In [124]:
import dataclasses
import pickle
import random
import numpy as np
import os
import re
import json
import time
from annoy import AnnoyIndex
from tqdm.notebook import tqdm
from scipy.spatial.distance import cdist, pdist, squareform, euclidean
import scipy
import scipy.stats as stats
from sklearn.decomposition import PCA
from scipy.spatial.distance import cosine as cos_dist
from sklearn.preprocessing import normalize
from gensim import models

from matplotlib import pyplot as plt
from typing import *
from collections import Counter

In [141]:
def read_goog_file(data_dir: str='.', size: int=None, clean=False) -> Tuple[List[str], np.array]:
    """
    Read the 3M vectors of length 300 from the Google News dataset. 
    
    Returns a list of words and a matrix of vectors. Indices match between the two.
    The vectors are normalized to unit, because Semantle uses cos distance which ignores magnitude.
    
    data_dir: dir that contains source files{"15.6 11.6 6.1": ["in"], "13.8 0.6 8.1": ["for"], "12.8 13.2 5.7": ["that"], "9.7 10.4 3.4": ["is"], "21.4 8.6 4.0": ["on"], "10.6 10.4 10.2": ["with"], "-3.2 6.4 6.6": ["said"], "9.4 6.1 4.9": ["was"], "22.3 10.1 9.2": ["the"], "7.9 0.8 5.5": ["at"], "5.3 15.9 5.8": ["not"], "10.5 15.0 6.7": ["as"], "18.1 15.9 10.2": ["it"], "7.8 9.1 5.9": ["be"], "10.4 7.4 4.4": ["from"], "13.8 8.8 7.6": ["by"], "5.9 8.7 4.1": ["are"], "7.5 10.4 5.7": ["have"], "6.5 18.0 6.4": ["he"], "11.6 5.9 4.7": ["will"], "14.8 4.4 1.6": ["has"], "6.2 9.1 3.7": ["his"], "15.0 -4.0 -0.6": ["an"], "9.5 1.8 9.0": ["this"], "10.7 11.4 12.5": ["or"], "11.9 10.8 4.4": ["their"], "1.1 8.4 3.8": ["who"], "8.8 17.7 6.2": ["they"], "4.2 13.8 13.4": ["but"], "7.3 7.0 6.6": ["had"], "10.0 -4.9 9.0": ["year"], "4.8 6.6 4.4": ["were"], "3.2 18.2 7.5": ["we"], "3.6 0.5 4.9": ["more"], "17.6 2.7 11.6": ["up"], "11.2 9.5 2.4": ["been"], "9.6 22.5 9.2": ["you"], "32.0 3.8 -0.5": ["its"], "12.3 16.9 12.4": ["one"], "8.6 1.4 5.9": ["about"], "11.8 9.6 6.3": ["would"], "18.5 4.6 8.6": ["which"], "11.5 12.0 5.3": ["out"], "6.5 17.2 9.0": ["can"], "8.6 16.7 9.8": ["all"], "12.2 5.7 6.4": ["also"], "6.4 7.7 9.5": ["two"], "15.7 4.5 4.1": ["after"], "11.6 4.5 7.6": ["first"], "2.9 17.0 10.5": ["do"], "-0.5 13.3 7.7": ["time"], "8.3 1.5 3.4": ["than"], "8.6 15.9 10.2": ["when"], "19.2 -1.5 2.6": ["over"], "12.0 -1.5 5.8": ["last"], "17.1 1.9 -2.5": ["new"], "6.2 13.9 7.7": ["other"], "4.9 3.9 4.9": ["her"], "11.7 15.6 7.4": ["people"], "14.5 6.1 0.3": ["into"], "4.3 18.6 6.2": ["our"], "-1.8 9.4 8.4": ["there"], "5.0 4.3 5.7": ["she"], "12.1 10.7 7.7": ["could"], "17.6 14.9 9.0": ["just"], "9.0 -0.0 1.1": ["years"], "10.7 7.1 8.7": ["some"], "5.0 6.1 9.0": ["three"], "16.6 -5.4 0.0": ["million"], "9.4 26.4 11.4": ["them"], "5.4 17.1 6.9": ["what"], "1.6 18.0 12.4": ["so"], "7.4 7.3 6.4": ["no"], "17.7 8.7 10.8": ["like"], "5.3 19.4 11.2": ["if"], "8.4 12.5 6.6": ["only"], "10.1 3.2 2.4": ["percent"], "0.3 11.5 7.9": ["get"], "3.8 7.6 2.9": ["did"], "6.1 22.0 7.2": ["him"], "6.1 18.1 11.6": ["game"], "10.7 10.3 6.4": ["back"], "0.9 13.1 11.1": ["because"], "14.4 10.5 5.4": ["now"], "10.2 8.1 2.8": ["before"], "41.9 2.7 0.0": ["company"], "8.9 12.4 4.3": ["any"], "6.2 11.1 4.4": ["team"], "6.0 18.4 0.9": ["against"], "15.5 7.8 10.2": ["off"], "3.6 8.0 2.3": ["most"], "9.6 1.6 0.3": ["made"], "9.2 6.0 5.6": ["through"], "8.7 3.6 4.1": ["make"], "6.0 3.0 9.6": ["second"], "5.3 6.5 12.1": ["state"], "8.9 5.1 0.2": ["well"], "5.0 11.7 13.0": ["day"], "0.9 5.2 11.1": ["season"], "-0.2 5.0 4.9": ["says"], "10.3 1.3 5.3": ["week"], "8.7 14.8 7.2": ["where"], "12.7 12.4 6.6": ["while"], "16.2 8.2 7.8": ["down"], "11.2 10.9 4.6": ["being"], "18.7 12.9 7.2": ["government"], "11.6 19.7 7.3": ["your"], "5.0 8.5 3.7": ["home"], "3.9 17.2 10.4": ["going"], "5.8 10.9 6.7": ["my"], "8.2 9.6 6.9": ["good"], "4.4 13.4 3.9": ["should"], "6.0 9.7 3.8": ["many"], "7.0 20.8 6.5": ["way"], "5.7 19.3 11.6": ["those"], "5.2 7.1 8.1": ["four"], "4.7 2.5 7.6": ["during"], "11.3 10.3 0.2": ["such"], "10.7 11.4 7.4": ["may"], "-4.6 11.2 2.6": ["very"], "4.8 15.1 10.4": ["how"], "7.7 11.6 3.4": ["since"], "0.2 3.2 2.1": ["work"], "6.8 0.9 0.8": ["take"], "8.8 -4.4 1.6": ["including"], "9.7 -4.2 3.6": ["high"], "11.5 17.0 12.7": ["then"], "12.4 -0.8 4.5": ["next"], "12.1 8.6 0.9": ["much"], "8.5 9.6 9.7": ["still"], "1.9 8.9 10.0": ["go"], "-1.8 12.0 6.8": ["think"], "14.8 -3.2 5.1": ["old"], "10.2 18.8 5.8": ["even"], "24.2 13.9 0.7": ["world"], "7.9 7.8 8.9": ["see"], "3.3 4.4 9.3": ["say"], "12.7 4.2 5.3": ["business"], "5.8 5.4 7.7": ["five"], "-4.5 2.4 0.1": ["told"], "9.1 3.4 5.6": ["under"], "4.5 26.1 7.7": ["us"], "1.7 14.7 9.5": ["these"], "6.1 15.5 7.2": ["right"], "6.3 17.4 9.3": ["me"], "5.0 8.5 8.6": ["between"], "0.8 10.3 4.2": ["play"], "6.4 5.7 3.0": ["help"], "16.6 5.4 5.2": ["market"], "-0.1 15.0 6.4": ["know"], "7.6 5.4 12.5": ["end"], "16.8 9.5 7.2": ["long"], "-3.3 1.6 1.8": ["information"], "-4.7 4.4 5.0": ["points"], "7.8 10.5 3.8": ["does", "annular"], "-1.3 12.3 8.4": ["both"], "11.2 3.7 4.1": ["part"], "16.8 4.7 9.8": ["around"], "1.2 13.4 5.4": ["police"], "2.2 13.5 6.0": ["want"], "18.1 -2.1 2.0": ["based"], "4.1 10.8 8.0": ["got"], "3.7 3.0 9.3": ["third"], "0.2 5.0 8.6": ["school"], "2.4 5.9 4.3": ["left"], "22.9 9.2 10.5": ["another"], "9.9 11.8 -1.0": ["country"], "-1.1 15.1 5.2": ["need"], "5.8 11.5 6.0": ["best"], "-1.9 6.7 2.2": ["win"], "14.5 1.6 4.4": ["quarter"], "10.3 8.3 -1.3": ["use"], "16.0 3.6 0.2": ["today"], "6.2 5.8 5.2": ["same"], "4.4 11.8 3.0": ["public"], "4.6 5.8 7.8": ["run", "unhurried"], "14.6 3.9 11.5": ["set"], "10.4 -1.1 9.1": ["month"], "15.8 0.6 6.0": ["top"], "27.3 0.5 1.7": ["billion"], "3.0 13.5 6.4": ["come"], "8.6 5.2 7.8": ["city"], "2.6 6.5 7.8": ["place"], "7.6 10.7 5.9": ["night", "piqueteros"], "5.8 4.2 8.5": ["six"], "6.9 10.8 15.5": ["each"], "2.6 10.1 9.2": ["here"], "19.7 5.9 -2.1": ["group"], "3.4 12.2 9.2": ["really"], "7.2 -3.7 2.4": ["found"], "10.6 8.4 4.0": ["used"], "4.8 8.4 1.6": ["lot"], "-0.6 -1.5 6.6": ["money"], "12.7 3.3 7.2": ["put"], "7.8 9.4 9.0": ["games"], "3.1 2.2 0.1": ["support"], "5.9 -8.4 2.5": ["program"], "10.0 0.1 8.9": ["half"], "1.5 5.7 4.7": ["report"], "2.0 8.9 4.7": ["family"], "5.2 3.4 2.9": ["months"], "2.2 9.5 0.8": ["number"], "14.4 1.1 2.5": ["officials"], "3.5 1.8 3.7": ["am"], "12.6 1.7 -4.9": ["former"], "16.8 19.4 8.0": ["own"], "20.4 18.3 9.0": ["man"], "0.6 15.2 9.6": ["too"], "5.2 8.0 5.8": ["better", "exerted"], "3.8 4.6 4.9": ["days"], "6.0 6.3 2.0": ["came"], "1.0 -1.8 -1.3": ["lead"], "7.1 11.8 7.2": ["life"], "10.6 1.3 7.7": ["show"], "10.5 0.9 2.8": ["past"], "7.4 -3.6 -2.8": ["took"], "-4.5 5.3 8.9": ["added"], "6.1 1.3 6.4": ["expected"], "7.8 5.7 4.2": ["called"], "11.9 10.1 4.1": ["great"], "14.9 -8.2 0.3": ["services"], "2.6 7.5 8.6": ["children"], "12.6 10.8 9.2": ["hit"], "6.2 11.5 7.7": ["area"], "16.8 5.6 2.0": ["system", "reshaped"], "13.9 7.7 8.7": ["every"], "4.6 1.0 8.7": ["pm"], "34.7 7.6 11.9": ["big"], "8.2 5.8 -2.4": ["service"], "7.6 8.4 4.0": ["few"], "7.6 -0.7 9.1": ["per"], "-3.1 8.6 0.9": ["members"], "8.1 4.2 4.8": ["early"], "-1.3 11.2 5.4": ["point"], "8.7 4.7 13.9": ["start"], "39.0 4.2 1.4": ["companies"], "12.7 5.5 13.5": ["little"], "3.7 8.1 2.6": ["case"], "10.0 -5.9 -0.8": ["ago"], "5.8 1.3 10.8": ["local"], "4.4 1.7 3.0": ["according"], "8.5 17.0 5.0": ["never"], "8.3 13.7 5.3": ["without"], "13.0 4.3 1.9": ["sales"], "4.1 7.2 10.9": ["until"], "2.6 3.4 3.9": ["went"], "3.8 11.2 5.3": ["players"], "1.2 1.5 2.0": ["won"], "8.3 2.7 3.4": ["financial"], "8.4 8.4 5.6": ["news"], "13.2 8.6 5.6": ["share"], "9.0 3.0 1.8": ["several"], "8.6 6.6 -1.4": ["free"], "8.9 10.7 0.1": ["away"], "15.3 6.6 7.1": ["already"], "29.6 1.9 3.9": ["industry"], "1.9 7.7 10.9": ["call"], "2.3 2.5 6.7": ["students"], "8.4 14.1 10.6": ["line"], "-4.2 1.4 -0.7": ["available"], "12.7 6.4 3.0": ["making"], "4.0 -1.2 0.1": ["held"], "7.8 2.2 6.5": ["final"], "8.4 14.1 7.6": ["power"], "12.8 11.3 9.4": ["plan"], "11.8 12.4 7.7": ["might"], "8.0 3.6 9.0": ["least"], "10.3 4.6 5.2": ["look"], "5.8 3.9 0.4": ["forward"], "-2.6 2.5 0.7": ["give"], "15.7 14.8 10.4": ["again"], "5.4 4.9 3.6": ["later"], "19.7 -2.2 5.0": ["full"], "5.3 20.1 8.0": ["must"], "1.8 15.4 4.7": ["things"], "25.4 3.5 -2.6": ["major"], "6.4 4.5 -2.7": ["community"], "17.2 -5.7 -2.7": ["announced"], "7.2 7.7 5.8": ["open"], "8.9 4.9 3.2": ["record"], "7.5 2.2 3.8": ["reported"], "12.4 3.6 4.4": ["court"], "3.2 3.7 -0.3": ["working"], "-1.5 9.9 2.7": ["able"], "5.8 16.6 7.8": ["something"], "8.0 7.2 -3.7": ["president"], "-2.7 1.3 5.5": ["meeting"], "4.5 13.2 1.4": ["keep"], "9.1 5.9 4.1": ["future"], "6.9 9.9 -0.9": ["far"], "18.4 3.0 -1.4": ["deal"], "6.6 -1.1 -2.2": ["development"], "6.3 7.7 6.3": ["find"], "3.2 9.4 9.6": ["times"], "6.8 6.9 -2.3": ["office"], "5.5 -0.5 3.8": ["led"], "1.2 4.0 3.3": ["among"], "0.3 3.6 2.0": ["increase"], "5.5 8.9 3.6": ["whether"], "10.4 1.2 5.2": ["cost"], "8.9 12.6 -0.3": ["security"], "6.6 12.1 9.1": ["job"], "0.8 2.2 4.9": ["less"], "17.0 6.8 7.2": ["head"], "3.7 5.5 7.2": ["seven"], "8.6 -1.0 5.0": ["growth"], "7.1 5.5 7.0": ["lost"], "13.5 -4.7 5.0": ["pay"], "7.4 1.6 7.2": ["looking"], "0.5 -1.3 -1.4": ["provide"], "20.0 0.8 5.0": ["plans"], "13.1 -2.2 3.0": ["products"], "-2.3 7.3 6.5": ["car"], "12.6 -3.4 2.1": ["recent"], "2.9 19.6 4.2": ["hard"], "2.3 23.3 6.8": ["always"], "10.2 -6.3 1.1": ["include"], "1.7 5.0 2.3": ["women"], "12.4 4.9 7.0": ["across"], "3.7 6.6 2.3": ["tax"], "5.3 12.0 24.1": ["water"], "5.6 5.9 6.0": ["continue"], "-0.3 11.2 -2.4": ["important"], "0.5 10.4 7.0": ["different"], "9.4 13.1 4.6": ["close"], "10.8 -1.1 6.9": ["late"], "3.6 6.1 4.2": ["decision"], "0.1 1.4 7.4": ["current"], "7.5 7.5 5.7": ["law"], "5.8 11.1 -0.6": ["within"], "10.7 3.3 7.2": ["along"], "1.1 5.0 -0.5": ["played"], "12.8 11.1 5.6": ["move"], "4.0 10.4 4.0": ["enough"], "9.0 5.7 0.2": ["become"], "15.0 13.6 8.9": ["side"], "10.7 1.7 -0.1": ["national"], "10.4 -1.7 6.1": ["results"], "-5.9 6.5 4.6": ["level"], "6.1 6.8 1.7": ["loss"], "5.5 6.4 11.7": ["economic"], "-0.4 7.0 2.0": ["coach"], "12.9 7.1 1.5": ["near"], "-0.5 12.7 7.8": ["getting"], "12.3 11.0 7.5": ["price"], "5.6 3.4 10.4": ["event"], "8.3 1.3 9.9": ["fourth"], "-0.8 8.4 5.2": ["change"], "23.5 5.9 9.8": ["small"], "8.5 3.1 3.9": ["board"], "-0.2 16.6 6.9": ["goal"], "5.3 3.4 -2.8": ["taken"], "10.3 7.0 0.5": ["field"], "10.2 1.1 7.5": ["prices"], "5.2 0.7 1.9": ["weeks"], "8.3 14.6 7.0": ["men"], "-2.8 2.3 4.8": ["asked"], "4.6 8.4 8.3": ["eight", "precipitating", "spoliation"], "4.9 -0.3 5.3": ["data"], "2.8 14.7 1.2": ["shot"], "12.8 -2.4 6.3": ["started"], "4.4 -4.2 0.9": ["director"], "3.3 15.0 7.6": ["party"], "7.8 3.1 13.3": ["federal"], "0.2 7.6 5.2": ["done"], "-2.4 18.5 10.3": ["political"], "2.4 4.5 2.1": ["minutes"], "9.5 1.6 0.5": ["taking"], "13.9 4.7 -0.3": ["technology"], "9.9 -4.0 2.8": ["project"], "21.7 -1.1 3.2": ["center"], "15.9 -5.5 -4.8": ["leading"], "-2.9 10.6 0.7": ["issue"], "6.0 9.7 9.8": ["though"], "10.1 12.4 6.7": ["having"], "-0.8 3.8 7.1": ["period"], "5.3 6.2 10.1": ["likely"], "-8.4 0.5 3.6": ["scored"], "12.2 2.0 0.9": ["strong"], "7.1 4.3 0.0": ["series"], "2.0 37.5 9.5": ["military"], "8.1 7.6 5.9": ["seen"], "5.8 15.5 6.9": ["trying"], "3.4 9.4 3.4": ["coming"], "3.0 2.7 7.5": ["process"], "10.5 12.5 6.4": ["building"], "12.0 12.8 1.2": ["behind"], "2.8 0.0 5.8": ["performance"], "7.9 -2.6 1.5": ["management"], "10.2 11.6 5.8": ["saying"], "11.5 -2.3 5.6": ["earlier"], "0.9 8.5 2.5": ["believe"], "17.6 6.3 20.0": ["oil"], "-3.4 -0.3 0.8": ["given"], "12.0 8.9 6.7": ["customers"], "1.6 -0.2 6.0": ["due"], "4.8 -0.1 3.4": ["following"], "-0.7 4.9 7.1": ["term"], "3.6 16.7 5.7": ["others"], "4.7 6.1 -6.2": ["statement"], "8.6 4.9 -1.3": ["international"], "11.5 7.0 9.3": ["economy"], "9.1 2.4 8.5": ["health"], "3.5 24.1 7.6": ["thing"], "-0.8 8.6 5.2": ["return"], "0.7 15.9 -0.5": ["killed"], "3.9 7.5 5.7": ["further"], "2.3 13.9 6.5": ["doing"], "13.3 19.7 14.9": ["face"], "1.9 1.9 5.5": ["low"], "6.3 -2.7 5.4": ["higher"], "15.8 1.5 -0.2": ["site"], "18.3 15.7 13.4": ["once"], "11.3 16.1 4.8": ["yet"], "2.8 4.0 -0.8": ["hours"], "6.9 13.0 0.1": ["control"], "-3.3 -2.0 -2.8": ["received"], "-5.9 3.8 2.9": ["rate"], "1.8 2.8 4.9": ["career"], "4.3 14.5 5.9": ["teams"], "3.0 10.2 0.6": ["known"], "6.4 -1.9 -1.8": ["offer"], "-1.5 8.9 9.8": ["race"], "13.7 16.6 6.1": ["ever"], "1.3 4.8 -2.6": ["experience"], "5.1 13.4 3.2": ["playing"], "11.8 11.3 -1.3": ["name"], "1.6 16.4 3.8": ["possible", "markswoman"], "9.8 7.3 -1.5": ["countries"], "4.7 4.8 5.3": ["average"], "4.8 4.6 5.8": ["together"], "17.3 11.1 4.7": ["using"], "8.3 3.4 11.8": ["cut"], "8.0 5.3 4.8": ["total"], "9.0 10.4 3.5": ["round"], "0.3 1.9 4.2": ["young"], "19.7 3.6 9.9": ["nearly"], "11.5 7.8 -0.2": ["shares"], "-5.1 10.7 1.9": ["member"], "5.2 13.4 -0.6": ["campaign"], "12.8 9.6 3.1": ["media"], "1.8 9.9 4.7": ["needs"], "4.0 12.8 4.2": ["why"], "5.4 7.9 11.0": ["house"], "-3.0 5.4 -1.9": ["issues"], "10.9 -0.4 5.3": ["costs"], "6.2 24.2 7.5": ["fire"], "-0.3 6.9 -2.5": ["victory"], "9.2 14.9 2.6": ["player"], "14.3 -2.4 6.3": ["began"], "1.1 10.2 9.5": ["sure"], "4.8 13.4 3.2": ["story"], "-0.6 2.9 3.7": ["staff"], "10.1 11.4 12.7": ["order"], "5.8 36.1 6.0": ["war"], "33.3 3.5 10.3": ["large"], "4.3 8.2 0.1": ["interest"], "13.1 13.0 11.7": ["stock"], "12.7 3.9 28.2": ["food"], "5.0 -1.1 0.7": ["research"], "6.0 8.5 3.7": ["key"], "10.8 4.4 8.7": ["morning"], "4.1 2.7 3.2": ["conference"], "-2.0 -1.9 -0.3": ["senior"], "21.9 3.4 1.0": ["global"], "1.8 14.6 1.7": ["death", "birthers"], "7.4 22.2 10.6": ["person"], "3.9 9.6 8.0": ["thought"], "0.2 -3.1 0.6": ["gave"], "4.7 9.2 7.9": ["feel"], "14.8 3.2 7.8": ["energy"], "10.8 8.7 0.5": ["history", "birthplace"], "15.1 -4.1 -1.6": ["recently"], "37.1 1.2 -0.1": ["largest"], "0.1 8.7 0.5": ["general"], "14.1 13.5 -0.5": ["official"], "5.3 5.0 -2.2": ["released"], "-0.3 6.2 3.4": ["wanted"], "-3.9 -1.6 6.0": ["meet"], "2.8 6.7 7.2": ["short"], "13.2 12.6 6.2": ["outside"], "7.5 6.0 1.8": ["running"], "7.2 6.3 10.4": ["live"], "0.2 14.3 9.2": ["ball"], "9.7 1.1 4.3": ["online"], "12.5 15.8 10.1": ["real"], "3.9 14.4 -2.0": ["position"], "3.8 13.5 2.5": ["fact"], "22.2 5.2 9.3": ["fell"], "4.3 6.6 7.2": ["nine"], "17.4 12.0 1.7": ["front"], "3.3 16.5 5.9": ["action"], "2.7 21.7 5.2": ["defense"], "3.3 18.5 3.4": ["problem"], "5.9 9.1 -2.5": ["problems"], "20.5 15.0 4.0": ["nation"], "-2.5 6.8 6.2": ["needed"], "5.0 4.8 2.8": ["special"], "17.3 11.3 10.9": ["almost"], "0.1 15.3 7.0": ["chance"], "1.3 7.7 6.0": ["result"], "6.1 4.7 2.3": ["reports"], "13.4 12.1 -4.1": ["leader"], "6.7 5.9 4.8": ["investment"], "14.9 -2.4 7.2": ["yesterday"], "7.6 10.7 -0.1": ["leaders"], "8.5 3.1 2.1": ["ahead"], "8.9 4.3 6.7": ["production"], "8.5 10.4 5.1": ["comes"], "3.1 2.6 3.8": ["runs"], "5.1 9.4 7.9": ["match"], "-0.8 5.0 -5.6": ["role"], "15.4 15.9 13.7": ["kind"], "4.5 16.2 9.4": ["try"], "7.9 2.2 11.4": ["ended"], "-5.0 13.9 3.2": ["risk"], "7.5 14.7 6.9": ["areas"], "-5.2 14.0 8.1": ["election"], "22.0 3.9 11.4": ["workers"], "-4.2 1.1 1.6": ["visit"], "6.9 5.1 3.3": ["bring"], "0.6 12.8 3.3": ["road"], "8.0 3.7 4.9": ["music", "hubbed"], "8.1 -2.8 1.2": ["study"], "10.5 5.6 3.8": ["makes"], "3.8 16.4 9.1": ["often"], "3.4 3.8 0.8": ["release"], "12.7 8.1 3.9": ["woman"], "0.1 8.0 6.8": ["vote"], "-1.5 2.7 2.9": ["care"], "7.7 5.8 2.6": ["town"], "5.9 10.0 1.8": ["clear"], "3.9 2.3 0.5": ["comment"], "-2.4 2.8 10.1": ["budget"], "11.4 9.7 4.1": ["potential"], "5.2 9.1 7.5": ["single"], "14.7 4.0 3.6": ["markets"], "6.1 15.5 2.9": ["policy"], "9.8 7.9 6.4": ["capital"], "13.8 2.1 7.4": ["saw"], "3.3 3.8 -4.9": ["access"], "2.6 4.2 2.9": ["weekend"], "11.1 11.9 0.1": ["operations"], "5.8 5.4 6.4": ["whose"], "15.6 8.3 8.5": ["net"], "6.5 11.4 7.7": ["hand"], "4.2 -0.7 0.5": ["increased"], "5.9 7.6 1.8": ["charges"], "0.1 4.0 2.8": ["winning"], "11.5 9.7 8.4": ["trade"], "-0.6 -0.1 8.6": ["income"], "6.5 10.8 2.7": ["value"], "-0.6 -0.5 2.3": ["involved", "opining"], "11.1 1.8 7.1": ["bill"], "3.6 0.4 4.7": ["compared"], "3.2 13.6 4.7": ["anything"], "10.6 -0.1 -0.2": ["manager"], "-3.8 8.2 7.3": ["property"], "12.9 12.4 7.0": ["stop"], "17.3 1.5 13.2": ["annual"], "7.7 3.8 -1.1": ["private"], "11.3 -8.3 1.9": ["contract"], "-0.3 9.7 -5.5": ["died"], "3.5 8.8 8.3": ["hope"], "1.2 3.8 4.3": ["product"], "10.0 13.7 2.5": ["fans"], "7.3 -2.1 8.9": ["lower"], "6.6 -1.6 4.1": ["demand"], "8.8 4.2 6.3": ["club"], "-1.7 6.1 -1.3": ["comments"], "-1.2 9.2 7.9": ["film"], "0.5 8.5 3.0": ["yards"], "0.6 -0.7 0.1": ["quality"], "6.7 2.1 -2.0": ["currently"], "1.4 -1.6 5.1": ["events"], "4.4 1.8 1.4": ["addition"], "11.7 6.6 9.7": ["couple"], "0.6 6.5 6.3": ["schools"], "3.6 29.5 -7.0": ["attack"], "9.3 6.5 7.6": ["region"], "19.4 3.0 1.7": ["latest"], "0.6 11.3 6.0": ["opportunity"], "6.1 -2.8 -2.8": ["worked"], "6.2 13.2 5.2": ["course"], "10.1 19.1 6.3": ["bad"], "12.5 8.8 15.2": ["fall"], "11.4 4.9 6.5": ["jobs"], "1.2 4.9 2.2": ["list"], "8.5 14.7 3.3": ["let"], "2.9 12.3 9.3": ["however"], "9.4 3.5 2.4": ["chief"], "-0.4 0.4 8.9": ["summer"], "3.1 -6.0 2.5": ["programs"], "9.2 -2.6 1.5": ["revenue"], "23.3 1.9 6.1": ["rose"], "0.7 1.1 7.3": ["previous"], "6.7 5.4 4.6": ["football"], "34.4 6.3 5.1": ["biggest"], "14.6 5.8 5.6": ["employees"], "-0.9 -0.2 3.4": ["changes"], "3.3 5.2 7.4": ["residents"], "3.7 22.7 9.3": ["means"], "10.7 1.2 -4.6": ["agreement"], "9.5 -5.9 2.8": ["includes"], "6.3 5.9 0.6": ["post"], "8.3 16.8 12.7": ["probably"], "14.0 -3.0 0.1": ["related"], "-7.2 9.7 0.3": ["training"], "1.6 6.4 3.0": ["allowed"], "6.3 5.6 2.8": ["class"], "8.4 5.1 14.7": ["bit"], "9.8 5.8 6.3": ["video"], "4.9 5.7 -1.0": ["sent"], "-5.2 4.9 3.3": ["education"], "1.3 3.9 9.2": ["states"], "16.4 12.0 7.9": ["straight"], "8.2 22.6 7.0": ["love"], "9.4 9.1 2.9": ["beat"], "9.3 0.1 5.8": ["hold"], "10.9 7.1 2.4": ["turn"], "2.8 0.2 5.5": ["finished"], "9.6 3.6 2.0": ["network"], "22.4 1.0 0.3": ["buy"], "5.2 15.3 1.2": ["foreign"], "0.1 13.1 4.8": ["especially"], "16.1 5.4 1.9": ["groups"], "7.1 8.7 3.3": ["wants"], "7.1 4.8 2.7": ["title"], "9.4 -7.6 5.8": ["included"], "14.2 -3.1 2.1": ["turned"], "14.5 7.4 11.0": ["bank"], "7.9 8.2 5.1": ["efforts"], "-1.3 12.6 -0.2": ["personal"], "17.5 3.0 6.7": ["businesses"], "-2.3 15.5 5.4": ["situation"], "-2.7 6.1 3.7": ["district"], "5.7 2.3 -0.7": ["allow"], "8.2 -2.1 0.3": ["helped"], "3.6 9.2 5.3": ["body"], "6.3 12.0 4.6": ["nothing"], "13.0 11.3 0.3": ["soon"], "6.7 5.4 -0.9": ["safety"], "13.8 14.0 3.3": ["officer"], "17.8 1.2 5.8": ["cents"], "0.4 4.9 2.4": ["additional"], "4.5 5.7 0.7": ["spokesman"], "4.7 13.7 5.5": ["wife"], "10.6 0.2 -2.2": ["showed"], "-0.2 11.4 6.0": ["leave"], "10.1 6.9 6.2": ["investors"], "-1.5 3.1 5.6": ["parents"], "-0.9 0.6 0.5": ["medical"], "10.7 1.3 10.7": ["spending"], "8.3 6.2 2.2": ["non"], "-1.6 19.5 4.5": ["matter"], "8.2 -0.5 -1.0": ["spent"], "1.1 10.6 7.3": ["child"], "5.7 15.3 6.1": ["effort"], "7.9 6.2 4.7": ["opening"], "2.4 22.0 8.6": ["either"], "4.9 4.3 2.6": ["range"], "-4.1 14.9 1.1": ["question"], "-6.5 12.0 7.3": ["goals"], "8.1 15.2 2.5": ["administration"], "-0.2 24.2 4.9": ["friends"], "3.3 16.5 3.1": ["himself"], "11.8 -0.2 3.5": ["shows"], "-1.7 16.5 3.1": ["difficult"], "5.2 8.4 11.2": ["kids"], "6.0 -5.5 2.5": ["paid"], "10.5 6.5 7.0": ["create"], "9.6 -3.0 8.0": ["cash"], "1.6 1.9 5.2": ["age"], "-0.7 11.5 3.4": ["league"], "9.9 11.6 9.2": ["form"], "-0.6 5.6 3.9": ["impact"], "6.2 6.9 3.9": ["drive"], "11.2 20.4 7.9": ["someone"], "4.1 3.5 -1.5": ["became"], "-4.0 5.4 1.4": ["stay"], "3.9 26.2 3.5": ["fight"], "12.9 4.1 -1.9": ["significant"], "34.4 1.5 2.4": ["firm"], "2.6 8.2 1.1": ["hospital"], "2.2 -1.4 3.1": ["charged"], "8.5 14.4 -0.7": ["operating"], "16.0 6.2 3.9": ["main"], "-4.2 9.1 4.5": ["book"], "4.7 1.2 4.3": ["success"], "5.3 9.6 2.2": ["son"], "8.0 10.5 4.8": ["trading"], "3.5 6.2 -0.3": ["focus"], "9.0 5.7 5.3": ["room"], "6.7 3.3 7.5": ["continued"], "12.6 15.4 7.8": ["everything"], "10.5 3.3 3.8": ["agency"], "8.4 0.7 3.7": ["brought"], "-0.8 7.8 4.0": ["talk"], "3.6 7.9 8.1": ["break"], "2.8 20.0 7.7": ["air"], "16.1 -0.1 3.9": ["software"], "8.5 -2.3 5.4": ["decided"], "8.0 11.4 6.8": ["ready"], "-2.7 0.9 -0.5": ["arrested"], "5.9 1.2 0.9": ["track"], "-0.1 -6.2 -0.6": ["provides"], "5.7 8.5 7.6": ["mother"], "5.8 15.2 4.1": ["base"], "5.1 1.1 -1.7": ["trial"], "2.1 13.7 3.5": ["phone"], "11.8 7.7 2.3": ["build"], "1.6 9.7 6.7": ["conditions"], "9.7 10.5 11.7": ["rest"], "5.5 8.6 5.9": ["terms"], "2.1 4.8 7.7": ["expect"], "9.4 2.9 3.8": ["despite"], "5.7 0.2 2.4": ["closed"], "6.6 0.8 9.5": ["starting"], "1.5 1.9 1.2": ["provided"], "5.6 8.8 4.5": ["pressure"], "-0.8 10.9 -3.2": ["lives"], "10.7 9.7 0.2": ["step"], "-1.2 6.2 1.2": ["remain"], "15.0 -0.5 3.0": ["similar"], "4.9 7.5 1.0": ["charge"], "-0.2 11.2 1.9": ["date"], "15.3 8.9 14.8": ["whole"], "3.8 15.4 12.8": ["land"], "15.5 1.4 9.6": ["growing"], "4.6 -3.5 3.2": ["projects"], "-2.0 2.4 4.9": ["cases"], "7.2 27.4 12.8": ["ground"], "8.3 4.7 4.6": ["legal"], "10.2 -7.1 2.0": ["agreed"], "2.1 13.4 6.0": ["tell"], "6.7 8.1 -4.8": ["test"], "10.2 16.1 9.4": ["everyone"], "2.0 12.1 13.6": ["pretty"], "13.9 4.3 6.5": ["authorities"], "12.4 10.4 11.8": ["above"], "7.4 2.1 0.8": ["moved"], "20.1 0.3 -2.6": ["profit"], "4.1 3.1 5.5": ["throughout"], "15.0 18.7 4.5": ["inside"], "4.3 17.6 6.6": ["ability"], "3.0 5.8 1.4": ["overall"], "-3.0 10.0 9.0": ["pass"], "1.9 15.2 6.1": ["officers"], "10.7 13.9 10.8": ["rather"], "9.8 15.9 8.3": ["actually"], "-5.5 2.8 11.9": ["county"], "-1.3 5.0 3.6": ["amount"], "2.0 -5.5 4.7": ["scheduled"], "6.6 16.7 1.2": ["themselves"], "3.6 13.3 -2.8": ["organization"], "0.5 4.8 -0.0": ["giving"], "-7.2 3.4 2.5": ["credit"], "7.1 11.2 2.2": ["father"], "1.3 3.0 12.7": ["drug"], "-0.3 8.0 -3.2": ["investigation"], "-0.6 7.9 5.1": ["families"], "-7.3 -3.3 9.6": ["funds"], "-2.9 5.7 7.6": ["patients"], "6.7 3.4 0.7": ["takes"], "14.0 6.0 1.5": ["systems"], "13.5 -0.1 7.8": ["complete"], "14.2 -1.0 -1.3": ["sold"], "3.2 8.8 2.1": ["practice"], "1.7 8.4 4.2": ["calls"], "8.6 25.9 5.0": ["force"], "1.6 2.2 5.8": ["student"], "6.3 16.2 6.2": ["idea"], "1.2 3.0 2.9": ["reached"], "-2.5 19.0 9.6": ["reason"], "-5.4 1.6 5.6": ["levels"], "16.5 6.5 7.9": ["space"], "13.4 10.4 8.7": ["competition"], "12.6 40.9 6.4": ["forces"], "23.4 4.8 1.3": ["sector"], "5.5 11.0 6.3": ["tried"], "3.9 14.6 9.4": ["common"], "-2.7 5.0 3.3": ["homes"], "13.4 2.5 5.7": ["stage"], "11.9 7.9 4.8": ["department"], "9.0 -0.7 -1.8": ["named"], "19.8 0.9 6.0": ["earnings"], "1.6 -9.1 -2.0": ["offers"], "18.5 4.5 1.6": ["star"], "5.3 15.4 11.9": ["certain"], "7.9 3.3 7.7": ["double"], "3.5 10.8 8.2": ["longer"], "3.7 1.4 7.2": ["followed", "ler"], "2.2 20.8 4.9": ["cause"], "5.6 -9.8 -6.1": ["signed"], "6.8 -0.8 5.3": ["committee"], "4.5 3.4 9.0": ["hour"], "-1.0 2.1 6.7": ["college"], "12.0 5.1 -2.2": ["users"], "8.7 3.4 1.3": ["sign"], "1.1 7.6 6.4": ["living"], "7.9 -0.8 0.6": ["failed", "tizzy"], "6.1 5.9 0.0": ["reach"], "9.2 15.2 1.3": ["quickly"], "-2.8 0.1 0.2": ["receive"], "8.0 3.7 3.8": ["debt"], "19.2 -0.8 2.0": ["sale"], "8.6 7.7 9.0": ["insurance"], "8.2 15.0 5.0": ["anyone"], "-0.4 9.4 11.6": ["tournament"], "11.8 2.1 9.1": ["gas"], "7.2 2.4 0.1": ["talks"], "4.6 8.2 -0.0": ["serious"], "1.4 5.0 4.4": ["required"], "19.2 3.4 1.5": ["sell"], "4.6 1.1 11.1": ["construction"], "-0.5 6.7 4.1": ["evidence"], "2.8 5.4 4.9": ["remains"], "15.7 8.2 13.3": ["black"], "6.5 10.4 14.2": ["below"], "-1.3 6.3 1.1": ["improve"], "10.7 8.2 4.8": ["crisis"], "2.0 3.5 -0.7": ["address"], "-3.5 7.4 -1.5": ["questions"], "6.4 15.8 2.8": ["easy"], "11.1 1.5 11.0": ["begin"], "10.1 10.6 3.6": ["view"], "-1.1 1.9 -0.0": ["heard"], "8.7 2.2 0.6": ["executive"], "11.0 -11.3 4.2": ["raised"], "14.0 7.7 6.5": ["store"], "5.6 8.8 10.1": ["gets"], "1.9 -0.7 -0.4": ["filed"], "34.5 8.4 9.5": ["huge"], "12.3 9.4 5.6": ["moving"], "9.7 11.3 4.6": ["seems"], "-5.9 0.5 3.1": ["met"], "17.9 6.6 6.0": ["thousands"], "6.5 1.2 2.2": ["solutions"], "-5.3 6.6 3.1": ["score"], "3.3 -1.0 3.2": ["content"], "-5.9 6.3 0.9": ["treatment"], "0.9 -8.7 0.8": ["offered"], "11.6 4.1 -1.1": ["built"], "7.2 8.1 3.7": ["hits"], "-0.3 1.7 2.3": ["present"], "7.5 23.9 -5.0": ["attacks"], "1.5 6.0 9.2": ["although"], "8.1 2.4 7.8": ["social"], "8.8 3.6 5.8": ["afternoon"], "-6.4 14.8 7.5": ["vehicle"], "-1.4 6.4 -5.4": ["read"], "13.3 12.2 7.2": ["example"], "15.1 1.4 7.0": ["rise"], "3.6 3.7 4.5": ["minute"], "17.6 8.0 8.0": ["banks"], "0.1 3.8 3.6": ["council"], "2.7 36.3 9.7": ["troops"], "-6.3 -0.9 2.0": ["rates"], "3.1 16.6 6.8": ["tough"], "8.3 -1.9 -0.3": ["works"], "4.9 4.5 8.5": ["fifth"], "0.8 12.8 3.0": ["knew"], "2.9 5.4 7.5": ["felt"], "4.3 -3.4 -0.5": ["website"], "1.1 -3.8 8.1": ["fund"], "0.8 1.1 -1.3": ["issued"], "8.6 13.7 0.7": ["immediately"], "10.4 1.5 -0.4": ["opened"], "4.4 8.9 8.7": ["goes"], "12.1 -2.3 2.1": ["proposed"], "3.8 2.8 6.5": ["happy"], "4.4 19.5 7.8": ["guys", "obstructionism"], "0.3 9.1 3.5": ["response"], "5.3 7.6 9.8": ["numbers"], "5.2 -3.8 4.1": ["benefits"], "-1.2 6.9 2.5": ["happened"], "12.6 8.3 14.7": ["light"], "3.2 0.0 -1.9": ["positive"], "11.3 0.9 -1.0": ["chairman"], "9.8 5.4 -2.4": ["claims"], "2.4 0.5 1.4": ["details"], "8.6 7.2 -2.8": ["accused"], "12.0 8.0 8.7": ["equipment"], "14.4 2.9 11.0": ["dropped"], "12.2 2.1 6.0": ["dollars"], "9.7 5.9 5.7": ["various"], "19.5 0.7 5.7": ["worth"], "10.7 1.6 4.3": ["judge"], "-3.2 5.6 6.7": ["considered"], "15.9 0.5 5.7": ["commercial"], "5.8 1.7 2.3": ["activities"], "-1.7 -4.3 8.5": ["funding"], "13.7 8.2 10.0": ["dollar"], "18.5 8.2 11.7": ["plant"], "14.7 10.2 -1.2": ["mobile"], "12.9 6.9 5.2": ["television"], "7.9 4.4 8.0": ["rules"], "15.4 2.1 -2.2": ["rights"], "2.2 -1.2 -0.9": ["review"], "0.9 10.1 5.8": ["quite"], "1.4 2.1 8.2": ["regular"], "-0.9 7.5 5.6": ["served"], "1.5 9.4 -0.2": ["kept"], "8.1 3.5 0.8": ["marketing"], "9.5 1.8 5.0": ["created"], "10.3 12.5 3.3": ["heart"], "-8.3 2.6 -0.8": ["wrote"], "3.8 7.8 5.3": ["prison"], "18.8 14.4 9.0": ["instead"], "0.6 0.5 2.1": ["concerns"], "8.3 -0.8 0.0": ["offering"], "1.7 5.0 1.8": ["returned"], "1.1 -0.4 2.4": ["benefit"], "9.9 -1.0 0.4": ["designed"], "5.6 -7.2 0.4": ["approved"], "19.1 8.8 13.2": ["foot"], "11.0 9.5 4.7": ["search"], "9.0 4.7 -0.5": ["miles", "zee"], "10.9 -2.1 4.5": ["planned"], "-1.0 9.7 6.0": ["driving"], "16.4 12.8 10.7": ["entire"], "2.9 3.7 -3.9": ["providing"], "10.9 0.2 5.7": ["host"], "1.9 7.2 6.4": ["ask"], "12.9 0.4 3.3": ["design"], "2.0 0.6 3.4": ["hearing"], "8.2 9.7 4.4": ["save"], "11.5 0.1 8.0": ["looked"], "-2.4 7.6 2.4": ["travel"], "9.1 -2.5 -1.4": ["successful"], "4.3 2.3 10.6": ["beginning"], "5.9 14.2 8.8": ["movie"], "-3.8 8.8 8.3": ["adding"], "5.7 8.4 4.8": ["forced"], "12.8 7.2 5.1": ["toward"], "-0.6 5.9 2.6": ["ensure"], "0.8 -1.7 3.1": ["passed"], "22.2 15.0 -1.7": ["unit"], "-2.1 11.2 6.2": ["happen"], "4.6 13.6 9.8": ["mean"], "-1.4 15.9 3.1": ["shooting"], "5.3 7.1 8.8": ["gone"], "3.7 9.3 2.9": ["winner"], "5.8 1.2 6.2": ["hopes"], "0.3 10.7 3.5": ["understand"], "5.7 6.6 3.7": ["planning"], "0.7 5.8 7.3": ["trip"], "7.6 -4.7 4.9": ["raise"], "15.0 6.4 3.9": ["owner"], "12.3 1.2 1.8": ["popular"], "4.8 -1.0 0.7": ["completed"], "2.8 17.5 8.0": ["ways"], "4.8 4.3 2.2": ["attention"], "11.6 13.7 10.4": ["feet"], "7.5 8.9 4.7": ["assets"], "3.1 7.5 9.6": ["traffic"], "8.4 9.0 6.4": ["environment"], "-4.8 7.3 -3.3": ["interview"], "13.7 7.4 3.8": ["consumers"], "7.7 21.5 5.5": ["hands"], "-8.5 5.5 1.3": ["contact"], "-1.2 8.0 5.4": ["cars"], "7.9 15.0 7.1": ["dead"], "7.7 -4.0 1.2": ["features"], "5.0 19.5 2.3": ["challenge"], "3.9 6.7 4.1": ["particularly"], "-1.1 3.6 7.1": ["basis"], "-6.6 10.7 -1.2": ["violence"], "15.8 12.1 1.6": ["stand"], "14.4 6.7 3.7": ["consumer"], "2.9 17.7 9.6": ["sense"], "-0.1 7.3 -2.1": ["attorney"], "2.8 9.1 6.6": ["driver"], "6.6 1.5 -0.2": ["highest"], "8.7 6.6 0.5": ["posted"], "1.9 1.5 6.9": ["finish"], "1.6 10.0 8.6": ["limited", "persists"], "2.7 17.7 -0.9": ["source"], "1.0 9.5 4.0": ["serve"], "10.3 10.7 6.0": ["spot"], "1.0 8.8 0.4": ["advantage"], "-7.3 8.6 6.5": ["scoring"], "1.3 18.4 8.3": ["words"], "7.5 -5.8 -1.1": ["applications"], "3.9 6.7 4.5": ["reduce"], "18.5 6.6 18.7": ["white"], "10.2 -1.4 0.5": ["appeared"], "25.7 14.9 -1.7": ["itself"], "1.9 9.4 4.8": ["fuel"], "9.7 22.3 8.6": ["simply"], "2.2 1.9 8.8": ["fiscal"], "2.7 8.1 0.7": ["plays"], "-0.2 7.1 5.5": ["account"], "-0.5 1.0 0.7": ["follow"], "0.6 4.8 1.0": ["statements"], "8.3 3.7 -3.2": ["organizations"], "2.5 6.7 4.7": ["pick"], "10.7 4.8 5.4": ["continues"], "-4.0 0.3 10.4": ["session"], "5.9 15.9 10.9": ["nuclear"], "6.8 6.2 1.9": ["seconds"], "6.0 6.1 1.5": ["daughter"], "5.9 -1.2 2.7": ["co"], "4.4 1.0 2.3": ["sports"], "7.8 6.2 7.6": ["caused"], "-0.7 6.0 3.3": ["injury"], "1.7 6.9 8.0": ["effect"], "14.6 6.2 3.3": ["selling"], "3.5 6.5 16.9": ["middle"], "3.4 2.0 7.3": ["cuts"], "14.3 6.8 14.7": ["drop"], "12.5 -1.4 -1.7": ["facility"], "7.9 18.3 2.3": ["true"], "5.2 20.8 5.5": ["target"], "4.3 0.3 2.7": ["consider"], "7.5 10.5 2.1": ["watch"], "-6.5 -2.2 1.5": ["noted"], "0.4 9.3 5.8": ["resources"], "-0.4 6.6 5.8": ["opportunities"], "14.0 23.6 4.7": ["strategy"], "1.2 7.0 4.8": ["learn"], "6.9 9.1 1.7": ["re"], "3.2 11.8 -3.5": ["message"], "-3.4 7.9 3.3": ["injured"], "7.1 5.4 3.7": ["parties"], "2.4 2.3 -1.5": ["seeking"], "1.9 1.3 12.0": ["missed"], "2.8 17.0 1.1": ["wrong"], "-1.6 3.1 -1.4": ["letter"], "18.5 3.7 9.6": ["looks"], "-1.7 17.7 8.8": ["individual"], "6.2 11.7 7.4": ["approach"], "1.7 13.6 4.4": ["damage"], "6.4 16.5 11.3": ["else"], "7.6 7.6 7.7": ["speed"], "1.4 17.5 2.1": ["mind"], "18.4 1.9 6.5": ["bid"], "-4.3 11.0 8.4": ["subject"], "7.6 1.1 2.9": ["ran"], "1.9 11.3 1.7": ["send"], "5.2 7.1 2.9": ["existing"], "4.3 11.3 9.7": ["fun"], "-5.4 5.5 5.6": ["innings"], "7.3 12.2 3.8": ["press"], "-1.0 11.5 7.9": ["voters"], "2.6 6.3 6.2": ["championship"], "3.2 9.7 6.3": ["leaving"], "1.3 -0.2 -0.0": ["earned"], "-2.4 14.9 4.1": ["effective"], "5.4 7.2 12.0": ["poor"], "3.2 27.7 6.5": ["friend"], "4.3 14.7 7.2": ["customer"], "4.8 4.2 3.3": ["solution"], "20.4 7.0 -0.6": ["corporate"], "7.5 6.7 -7.4": ["independent"], "1.2 11.5 -1.5": ["leadership"], "17.1 19.3 12.7": ["human"], "1.2 15.8 4.3": ["shots"], "-2.2 3.8 2.8": ["believes"], "15.6 9.0 7.8": ["computer"], "17.5 0.2 2.9": ["s"], "1.8 3.5 9.9": ["items"], "2.9 8.0 5.3": ["confidence"], "5.6 -0.4 10.1": ["add"], "0.3 -1.7 2.9": ["award"], "12.1 8.1 7.6": ["parts"], "8.8 7.4 12.0": ["cover"], "2.4 3.4 6.3": ["missing"], "15.7 6.3 7.3": ["fast"], "1.4 10.6 1.9": ["incident"], "5.8 9.2 8.1": ["husband"], "3.1 6.2 2.0": ["responsible"], "7.7 6.3 1.1": ["losses"], "13.7 4.3 7.4": ["estimated"], "7.7 2.6 3.3": ["approximately"], "11.6 25.2 13.2": ["guy"], "17.5 3.3 -2.1": ["purchase"], "4.2 6.2 -3.3": ["helping"], "17.6 11.8 5.7": ["finally"], "7.6 0.3 4.4": ["spend"], "4.1 12.6 9.2": ["scene"], "2.7 22.8 2.8": ["opposition"], "5.7 6.1 0.2": ["develop"], "5.4 14.2 3.9": ["certainly"], "2.8 3.3 5.4": ["extra"], "2.9 10.1 3.7": ["talking"], "2.2 4.1 15.4": ["spring"], "-0.7 13.0 7.9": ["emergency"], "9.7 7.6 -1.9": ["station"], "3.2 -2.1 2.3": ["check"], "6.0 39.0 6.1": ["soldiers"], "-5.7 12.6 3.7": ["vehicles"], "14.6 3.7 2.4": ["launch"], "-2.1 13.1 -0.4": ["critical"], "-1.8 -1.9 -1.3": ["professional"], "3.7 2.0 5.3": ["described"], "-1.4 13.7 0.7": ["choice"], "4.6 20.7 10.7": ["moment"], "23.8 4.7 11.6": ["size"], "0.2 4.0 2.1": ["changed"], "20.5 4.2 6.9": ["holding"], "3.4 13.0 6.0": ["door"], "2.2 -2.4 3.9": ["declined"], "14.2 0.6 -1.9": ["launched"], "-1.1 10.0 4.3": ["condition"], "-0.0 10.8 8.8": ["lose", "bucketed"], "4.1 -0.0 -6.1": ["joined"], "-2.5 1.6 -1.0": ["gives"], "3.6 3.7 -2.3": ["developed"], "5.9 22.2 -0.5": ["protect"], "-0.6 5.2 3.2": ["girls"], "10.7 12.4 1.2": ["operation"], "0.4 19.4 5.8": ["necessary"], "-3.1 7.3 6.3": ["taxes"], "17.1 0.5 2.2": ["sites"], "6.0 3.5 3.4": ["beyond"], "7.0 8.9 7.9": ["daily"], "6.3 3.1 9.3": ["yard"], "5.4 9.1 5.8": ["calling"], "0.8 7.9 8.7": ["options"], "19.2 7.6 12.9": ["stocks"], "13.4 3.5 5.7": ["newspaper"], "3.9 17.0 8.9": ["peace"], "9.0 4.6 3.7": ["proposal"], "8.9 7.1 -0.2": ["previously", "pressurises"], "22.5 0.6 0.7": ["owned"], "6.4 2.1 0.3": ["regional"], "-0.2 3.8 1.0": ["hear"], "-2.7 -0.8 10.8": ["housing"], "10.4 6.4 3.2": ["owners"], "4.4 12.3 4.9": ["exchange"], "4.3 7.3 0.8": ["majority"], "9.0 4.5 15.6": ["starts"], "3.4 14.3 4.3": ["victims"], "14.4 0.6 1.9": ["model"], "7.3 2.4 0.1": ["struck"], "-0.5 8.3 6.6": ["tour"], "-1.9 2.1 5.2": ["basketball"], "0.7 4.3 -3.0": ["published"], "4.5 5.9 7.8": ["twice"], "-6.3 8.0 2.2": ["candidates"], "6.1 8.4 13.9": ["population"], "1.5 5.3 7.8": ["evening"], "-0.5 7.4 6.7": ["lack"], "11.9 8.6 2.4": ["north"], "1.0 31.2 4.4": ["fighting"], "-2.1 15.1 5.7": ["reporters"], "-5.2 2.1 2.3": ["concerned"], "10.2 7.9 4.5": ["south"], "13.9 -0.4 11.4": ["fine"], "5.4 14.8 15.5": ["weather"], "8.7 6.5 2.1": ["figures"], "5.9 9.1 9.8": ["floor"], "2.0 8.2 -0.5": ["relationship"], "7.4 2.8 7.8": ["activity"], "3.0 5.0 10.5": ["remaining"], "4.3 11.2 2.2": ["believed"], "6.9 -1.7 -3.5": ["confirmed"], "10.3 15.1 2.0": ["anti"], "7.8 -0.4 4.7": ["placed"], "7.7 8.4 12.4": ["caught"], "-2.1 20.4 8.8": ["crime"], "5.6 14.1 6.9": ["crowd"], "7.2 2.5 1.7": ["appear"], "15.6 -0.3 3.4": ["version"], "8.2 7.6 5.7": ["girl"], "4.1 3.9 -1.7": ["join"], "-0.4 -6.1 2.8": ["discuss"], "3.0 7.6 6.2": ["church"], "6.7 3.0 6.3": ["original", "joule"], "12.0 6.4 7.9": ["aid"], "5.9 6.4 7.9": ["expectations"], "5.8 0.9 3.3": ["clients"], "7.1 3.3 -5.3": ["located"], "3.9 7.2 16.3": ["gold"], "7.3 17.4 5.0": ["killing"], "0.5 11.1 6.7": ["specific"], "3.0 14.8 4.7": ["act"], "10.9 14.0 3.8": ["partner"], "4.4 7.6 7.2": ["losing"], "7.3 7.7 -0.9": ["claim"], "2.1 1.5 2.4": ["records"], "-6.3 13.4 2.9": ["offense"], "17.7 11.5 3.6": ["alone"], "7.7 0.8 -0.6": ["facilities"], "21.2 3.8 -2.8": ["division"], "20.6 2.7 2.5": ["retail"], "9.8 17.4 5.0": ["worst"], "7.4 4.7 5.3": ["legislation"], "7.1 4.1 5.4": ["page", "rollouts"], "3.2 4.0 6.0": ["measures"], "13.5 7.2 -6.7": ["brand"], "5.7 0.3 3.9": ["expects"], "13.6 6.5 11.2": ["art"], "2.7 1.2 -1.2": ["standards"], "6.3 0.6 0.8": ["application"], "15.6 4.2 1.3": ["central"], "4.1 3.7 9.8": ["sixth"], "1.4 10.8 -0.2": ["safe"], "15.7 7.6 9.2": ["style"], "-6.2 10.0 8.8": ["elections"], "0.4 8.4 8.1": ["primary"], "6.4 5.5 0.9": ["greater"], "2.9 6.0 5.7": ["progress"], "5.2 2.6 6.0": ["managed"], "8.5 4.1 6.7": ["supply"], "2.0 6.4 3.1": ["gain"], "-1.5 2.4 2.9": ["prior"], "3.0 -0.1 2.0": ["wins"], "2.8 -1.4 9.0": ["recovery"], "12.2 16.8 7.0": ["upon"], "11.0 1.5 9.4": ["plus"], "14.7 13.6 9.0": ["type"], "14.2 -0.6 13.7": ["paper"], "7.3 15.4 6.4": ["attempt"], "4.3 -0.4 -0.7": ["focused"], "3.4 2.5 -6.2": ["claimed"], "8.5 4.5 2.1": ["survey"], "-5.6 11.1 0.9": ["injuries"], "8.9 7.9 5.8": ["street"], "12.0 8.0 5.5": ["stores"], "11.2 5.1 8.0": ["block"], "15.6 5.3 3.0": ["analysts"], "1.9 4.0 -1.7": ["allows"], "20.7 6.9 4.7": ["hundreds"], "4.8 17.6 8.0": ["avoid"], "1.5 8.4 11.8": ["governor"], "12.2 10.9 7.9": ["figure"], "4.1 10.0 6.1": ["band"], "2.1 13.4 4.6": ["option"], "8.8 18.4 6.4": ["lines"], "-1.4 13.1 -0.6": ["sources"], "2.9 2.4 6.1": ["domestic"], "2.4 17.4 10.3": ["knows"], "8.5 7.7 3.8": ["seem"], "7.4 -1.8 0.7": ["feature"], "8.1 10.9 7.0": ["walk"], "6.1 4.7 7.2": ["broke"], "-3.0 6.6 8.3": ["factors"], "9.8 27.1 1.6": ["battle"], "6.3 7.2 -2.3": ["developing"], "3.3 29.8 0.9": ["threat"], "15.5 4.6 -1.5": ["worldwide"], "-6.1 0.4 -3.5": ["written"], "-1.6 8.4 -6.1": ["committed"], "17.8 7.5 11.6": ["green"], "8.8 5.3 5.4": ["agencies"], "1.6 1.8 -0.8": ["improved"], "19.8 3.1 12.8": ["traditional"], "11.5 3.5 9.1": ["fair"], "3.2 15.5 6.8": ["border"], "-2.5 11.6 4.4": ["concern"], "5.5 2.6 1.8": ["mark"], "5.5 7.3 1.6": ["allowing"], "6.6 3.0 -0.1": ["capacity"], "16.1 8.0 7.2": ["putting"], "12.6 7.2 4.5": ["appears"], "0.6 8.4 2.2": ["stories"], "10.1 3.2 9.5": ["grow"], "11.5 1.1 2.3": ["unique"], "6.4 16.0 9.1": ["favorite"], "8.1 6.0 9.9": ["nice"], "7.3 11.1 9.0": ["measure"], "1.5 3.0 3.4": ["debate"], "4.6 12.4 1.2": ["direct"], "9.1 5.1 4.5": ["stopped"], "8.9 8.2 6.9": ["index"], "-6.2 5.6 11.1": ["drugs"], "3.0 -0.6 4.7": ["tied"], "16.5 3.8 12.4": ["rising"], "2.3 15.7 3.6": ["risks"], "6.8 -0.0 11.2": ["mid"], "-1.3 4.0 3.8": ["arrived"], "3.9 8.2 4.1": ["communities"], "6.4 8.5 3.3": ["increasing"], "-0.9 -5.7 0.8": ["presented"], "14.0 8.6 8.8": ["boy"], "8.1 0.9 2.0": ["standard"], "2.3 13.2 3.6": ["prevent"], "-0.1 22.2 -0.5": ["mission"], "13.5 13.1 17.0": ["deep"], "3.8 15.8 11.7": ["word"], "-1.5 4.4 1.0": ["identified"], "11.8 -1.3 6.5": ["pulled"], "-1.4 7.6 9.6": ["inning"], "-8.6 11.0 1.5": ["difference"], "12.1 8.4 9.1": ["pair"], "0.4 11.0 -0.8": ["suffered"], "12.2 4.1 6.3": ["perfect"], "7.4 7.4 -1.9": ["advanced"], "1.8 12.6 10.2": ["prepared"], "6.6 6.9 3.4": ["fully"], "3.3 11.2 8.8": ["blood"], "11.6 1.3 3.4": ["signs"], "16.9 7.0 1.3": ["showing"], "3.9 -1.9 -0.8": ["interested"], "4.5 3.0 6.7": ["material"], "-3.4 9.5 4.7": ["article"], "15.8 -2.0 1.5": ["experts"], "12.9 7.8 20.0": ["bottom"], "1.4 14.0 -1.2": ["answer"], "2.4 13.8 15.7": ["usually"], "0.0 11.3 5.4": ["wait"], "-3.5 -0.3 -4.9": ["spoke"], "6.7 8.7 3.3": ["laws"], "1.9 6.2 5.6": ["request"], "6.7 16.7 0.6": ["units"], "-0.6 -3.1 5.7": ["loan"], "8.0 10.8 0.4": ["directly"], "4.8 7.7 0.3": ["union"], "7.8 11.2 7.0": ["particular"], "2.9 5.4 8.7": ["baseball"], "-0.4 -0.1 6.2": ["loans"], "9.0 0.4 7.8": ["pre"], "1.4 3.5 -0.9": ["born"], "-0.4 5.7 6.9": ["affected"], "3.1 11.9 6.4": ["waiting"], "10.6 10.5 5.1": ["simple"], "-0.5 -0.6 2.5": ["picked"], "13.6 10.8 10.1": ["faces"], "11.0 6.6 -3.2": ["names"], "8.6 5.8 -2.7": ["generation"], "2.1 11.5 -1.9": ["responsibility"], "6.6 5.3 7.3": ["combined"], "3.2 14.3 4.9": ["audience"], "3.3 12.0 11.7": ["hurt"], "8.7 3.1 5.0": ["seemed"], "16.5 14.4 18.8": ["red"], "10.6 -0.4 1.6": ["revenues"], "-7.8 14.8 1.0": ["candidate"], "6.1 9.5 0.2": ["ranked"], "11.5 7.2 8.8": ["cities"], "3.2 14.2 4.8": ["places"], "7.5 2.0 2.5": ["ruling"], "-5.2 4.3 -1.3": ["speak"], "0.6 17.2 3.0": ["strike"], "3.2 2.8 0.9": ["documents"], "5.2 21.5 13.2": ["sometimes"], "2.2 2.8 8.5": ["seasons"], "12.3 6.3 -1.1": ["via"], "7.0 5.6 2.1": ["carry"], "3.7 9.0 6.0": ["boys"], "10.2 12.2 7.4": ["facing"], "-0.2 4.8 4.7": ["learned"], "2.2 2.4 4.2": ["hotel"], "4.6 0.5 0.7": ["produced"], "12.1 9.8 10.7": ["seeing"], "1.1 8.5 2.7": ["seat"], "8.2 3.6 7.7": ["produce"], "19.9 6.5 4.9": ["millions"], "15.5 6.1 5.2": ["box"], "-5.5 10.9 6.7": ["decisions"], "4.7 3.8 4.6": ["coverage"], "-1.1 10.5 8.3": ["voice"], "7.7 6.8 8.2": ["rule"], "-4.7 11.8 5.3": ["respect"], "6.1 14.0 11.7": ["cancer"], "8.1 3.7 -5.9": ["shown"], "5.1 12.9 2.0": ["fired"], "13.1 5.6 3.6": ["decades"], "-2.7 9.3 4.8": ["reasons"], "4.5 11.0 8.5": ["tonight"], "5.2 4.6 -3.4": ["commitment"], "7.1 3.8 -2.8": ["alleged"], "6.0 6.5 5.4": ["competitive"], "-1.4 2.0 8.5": ["rebounds"], "1.0 12.9 1.9": ["individuals"], "4.2 16.3 8.0": ["thinking"], "-1.5 2.7 0.7": ["established"], "0.2 1.9 0.2": ["books"], "10.6 0.9 4.0": ["approval"], "5.5 3.6 -4.3": ["deliver"], "-0.4 0.5 1.1": ["remained"], "3.3 14.6 0.8": ["guard"], "8.0 8.2 3.7": ["infrastructure"], "3.3 2.6 1.7": ["appeal"], "10.4 -0.6 0.9": ["digital"], "12.9 1.3 9.7": ["ordered"], "8.0 17.6 0.2": ["citizens"], "1.3 10.1 3.4": ["speech"], "13.2 6.5 6.6": ["push"], "4.4 2.7 -1.8": ["highly"], "7.9 2.3 10.4": ["decline"], "3.2 3.1 11.4": ["holiday"], "10.1 9.2 8.1": ["self"], "4.6 7.2 1.4": ["accident"], "1.1 13.3 3.4": ["radio"], "3.4 3.5 3.1": ["require"], "-3.9 13.8 1.3": ["murder"], "12.9 6.4 6.2": ["wide"], "4.0 10.8 2.8": ["policies"], "17.7 6.3 10.7": ["park"], "9.4 6.7 2.4": ["champion"], "16.2 4.3 2.1": ["platform"], "-0.2 -3.0 -1.9": ["pleased"], "20.8 13.1 11.5": ["heavy"], "16.0 12.2 8.6": ["eventually"], "7.3 4.6 0.3": ["crash"], "7.3 8.1 0.3": ["minister"], "10.3 7.6 11.4": ["hot"], "1.2 8.5 6.9": ["serving"], "3.4 2.0 2.6": ["asking"], "-0.3 12.0 1.1": ["keeping"], "22.6 1.4 -2.2": ["provider"], "8.2 8.8 1.7": ["partners"], "0.3 13.2 0.2": ["remember"], "-1.3 8.4 0.1": ["seek"], "17.6 11.3 5.4": ["manufacturing"], "-3.8 8.7 10.2": ["teachers"], "10.5 5.0 0.7": ["towards"], "15.7 3.1 5.7": ["buying"], "12.1 7.8 0.6": ["warned", "positioned"], "12.2 9.3 5.7": ["initial"], "13.4 -4.4 13.8": ["pounds"], "2.2 11.3 8.2": ["brother"], "12.9 -7.7 6.4": ["panel"], "5.7 5.4 0.3": ["becoming"], "6.4 5.0 0.4": ["entered"], "7.2 11.2 9.6": ["sides"], "2.0 20.9 11.1": ["victim"], "12.4 5.4 6.6": ["setting"], "6.2 3.8 8.2": ["environmental"], "-0.4 1.7 7.7": ["bus"], "0.5 -6.7 4.0": ["note"], "7.4 1.5 -0.8": ["carried"], "8.5 5.7 9.2": ["consecutive"], "-1.8 1.6 8.9": ["older"], "1.4 20.7 3.1": ["criminal"], "21.1 -3.9 -1.0": ["bought"], "13.2 2.7 -0.2": ["announcement"], "15.0 1.4 4.4": ["decade"], "7.1 4.1 5.3": ["clean"], "-10.7 6.2 -5.7": ["stated"], "0.0 6.4 6.3": ["penalty"], "13.9 -0.1 4.1": ["boost"], "-11.8 -5.4 -0.2": ["attend"], "15.8 7.8 0.7": ["separate"], "2.7 5.9 7.3": ["enjoy"], "9.6 5.6 12.8": ["table"], "0.2 6.1 4.8": ["analysis"], "4.2 12.3 9.3": ["skills"], "0.5 4.5 5.0": ["jail"], "4.6 10.9 -1.8": ["protection"], "10.8 8.2 3.2": ["analyst"], "13.0 2.7 8.0": ["mostly"], "10.7 -1.5 3.1": ["paying"], "5.1 10.0 4.7": ["draw"], "8.3 15.9 8.9": ["perhaps"], "-0.7 12.4 -1.7": ["reading"], "1.0 5.5 3.7": ["cross"], "7.6 5.8 3.3": ["commission"], "2.6 3.5 8.8": ["drivers"], "9.4 -3.5 -1.7": ["offices"], "15.0 9.5 0.1": ["presence"], "-4.1 4.2 3.4": ["meetings"], "-4.3 9.1 5.6": ["votes"], "12.6 14.8 3.4": ["strength"], "7.7 2.0 6.1": ["delivery"], "7.7 15.3 -0.9": ["location"], "0.2 11.5 -0.2": ["positions"], "1.9 -2.9 -3.2": ["regarding"], "4.8 2.5 8.4": ["hoping"], "-4.9 24.5 3.5": ["offensive"], "8.4 11.8 4.9": ["spread"], "-3.7 16.8 5.5": ["whom"], "-0.8 7.3 4.0": ["deficit"], "19.5 15.0 -1.1": ["powerful"], "4.7 2.6 6.2": ["continuing"], "9.2 10.4 14.6": ["natural"], "10.4 -0.9 -1.3": ["revealed"], "6.2 16.0 12.4": ["feeling"], "9.9 -3.5 4.0": ["grew"], "11.9 10.1 4.4": ["watching"], "4.1 -0.9 1.8": ["suggested"], "13.9 6.3 14.1": ["slow"], "3.2 15.4 1.5": ["challenges"], "24.5 5.5 10.3": ["larger"], "10.2 9.9 4.4": ["quick"], "1.9 11.9 8.8": ["definitely"], "-2.2 12.3 7.6": ["flight"], "8.0 2.3 5.5": ["university"], "-4.1 0.0 3.4": ["junior"], "5.6 12.0 8.4": ["inflation"], "6.7 19.2 10.9": ["ones"], "2.1 11.2 -2.6": ["honor"], "-0.5 5.7 -3.1": ["active"], "0.7 0.8 0.5": ["voted"], "14.0 -1.1 10.5": ["solid"], "0.8 5.8 5.7": ["determine"], "2.4 2.3 9.5": ["reduced"], "2.1 -9.4 6.8": ["fees"], "0.7 11.0 4.8": ["multiple"], "2.9 4.7 6.3": ["decide"], "16.3 4.6 6.1": ["advertising"], "2.7 7.9 5.5": ["language"], "-2.5 -5.8 -4.0": ["expressed"], "9.4 9.3 3.5": ["steps"], "7.8 15.7 4.3": ["easily"], "10.5 5.6 1.2": ["bringing"], "1.1 13.1 6.6": ["physical"], "4.0 10.4 13.2": ["throw"], "14.5 6.9 7.0": ["forecast"], "-3.7 0.7 1.5": ["schedule"], "3.8 3.6 -3.1": ["denied"], "4.9 6.7 4.7": ["finding"], "13.2 -2.6 6.2": ["ban"], "-3.8 1.2 4.6": ["agree"], "10.0 -0.3 -2.3": ["section"], "0.7 3.4 0.9": ["admitted"], "-0.9 19.4 1.5": ["actions"], "1.4 0.6 11.4": ["normal"], "6.3 6.3 -3.6": ["devices"], "-5.5 12.2 -1.7": ["squad"], "11.6 9.7 7.6": ["creating"], "9.6 3.0 2.2": ["walked"], "2.7 11.1 1.5": ["streets"], "7.8 17.5 8.3": ["clearly"], "19.8 3.0 -1.7": ["complex"], "4.1 4.4 -2.3": ["lawyer"], "-12.0 11.0 -0.4": ["elected"], "0.5 0.7 4.8": ["increases"], "7.4 5.2 6.4": ["estimates"], "3.6 -1.9 -2.6": ["excited"], "0.2 2.0 3.1": ["helps"], "3.2 2.9 3.3": ["relief"], "-0.3 11.0 7.8": ["determined"], "9.2 10.9 12.0": ["maybe"], "3.6 19.0 9.7": ["suspect"], "11.7 8.1 8.6": ["sound"], "12.2 8.4 11.2": ["piece"], "11.2 1.9 2.6": ["campus"], "11.3 9.0 12.7": ["southern"], "1.8 7.4 0.8": ["degree"], "20.2 6.4 11.4": ["smaller"], "1.8 2.1 2.7": ["status"], "8.4 -0.5 4.7": ["headed"], "5.6 -0.3 16.8": ["healthy"], "43.5 7.9 9.8": ["massive"], "6.4 -2.4 -2.8": ["testing"], "15.7 3.8 0.2": ["distribution"], "8.0 16.7 5.2": ["completely"], "22.2 3.8 0.8": ["onto"], "9.7 14.1 7.2": ["hitting"], "4.4 3.2 4.6": ["closing"], "9.7 6.4 11.1": ["lawmakers"], "9.3 3.2 14.4": ["fresh"], "-1.7 8.1 21.5": ["winter"], "9.5 5.8 10.2": ["contest"], "-1.3 2.7 0.3": ["outstanding"], "7.4 10.3 4.0": ["exactly"], "-0.9 9.4 1.7": ["percentage"], "-1.0 -2.0 8.3": ["contributed"], "5.7 18.0 6.7": ["movement"], "13.1 13.4 11.6": ["storm"], "3.9 3.4 8.2": ["seventh"], "6.8 27.5 12.6": ["fear"], "3.5 2.8 9.7": ["weight"], "6.4 5.4 -3.0": ["secure"], "0.9 1.1 -0.0": ["conducted"], "19.0 9.0 -3.5": ["acquisition"], "-3.3 6.3 -0.5": ["maintain"], "5.9 2.9 4.2": ["rally"], "-2.5 14.8 4.1": ["knowledge"], "-1.8 7.2 1.8": ["recorded"], "1.3 5.5 -0.2": ["assistant"], "0.2 7.3 4.2": ["doctors"], "6.9 5.7 -5.3": ["proud"], "-2.1 3.8 1.5": ["advice"], "7.8 1.7 -1.2": ["finance"], "-0.5 6.8 7.8": ["sex"], "5.4 0.7 1.2": ["refused"], "1.9 12.6 3.4": ["agent"], "-4.5 6.8 4.0": ["draft"], "5.3 8.7 10.1": ["pitch"], "3.8 15.8 0.9": ["supporters"], "9.4 9.7 3.9": ["user"], "7.3 5.4 6.7": ["presidential"], "8.4 0.1 5.8": ["tie"], "16.8 11.0 13.3": ["sort"], "2.6 19.2 16.7": ["disease"], "6.3 7.1 6.7": ["tomorrow"], "12.9 9.1 5.5": ["core"], "0.7 12.0 7.0": ["willing"], "-1.9 14.2 11.6": ["patient"], "8.3 -2.3 3.0": ["considering"], "31.4 2.8 5.7": ["firms"], "0.7 1.4 2.2": ["technical"], "6.4 10.3 3.2": ["trouble"], "12.0 11.3 3.3": ["picture"], "-5.7 9.7 1.9": ["extremely"], "1.0 0.8 3.2": ["confident"], "1.4 18.3 11.7": ["count"], "7.3 8.6 10.3": ["visitors"], "1.8 -1.5 2.4": ["extended"], "9.3 14.5 7.4": ["reality"], "9.3 2.3 1.5": ["expand"], "11.5 4.6 -0.7": ["expansion"], "-1.7 2.3 1.0": ["lived"], "11.0 0.0 6.6": ["downtown"], "1.1 9.6 7.1": ["doubt"], "7.9 15.4 10.7": ["nature"], "3.5 2.4 3.9": ["listed"], "-3.3 5.3 0.0": ["leads"], "-0.2 14.0 4.8": ["opinion"], "13.3 2.9 4.9": ["row", "epiretinal"], "2.0 11.6 2.8": ["fellow"], "11.4 10.4 1.1": ["corner"], "-7.1 7.4 1.8": ["author"], "17.3 13.1 3.4": ["screen"], "13.8 12.2 4.3": ["shareholders"], "7.3 11.3 9.9": ["faced"], "13.3 11.6 18.1": ["plants"], "-7.4 8.2 2.8": ["arrest"], "7.7 14.5 8.6": ["society"], "0.6 21.7 4.5": ["character"], "3.5 7.4 4.3": ["labor"], "6.7 1.6 0.9": ["gains"], "10.3 9.0 8.2": ["science"], "2.4 7.6 10.3": ["teacher"], "10.4 1.9 3.7": ["web"], "5.9 5.1 24.8": ["restaurant"], "2.3 11.5 5.3": ["learning"], "7.5 6.4 10.1": ["recession"], "9.4 -1.1 6.4": ["raising"], "6.6 10.2 2.0": ["failure"], "2.4 12.4 4.0": ["airport"], "-0.9 28.2 -1.9": ["intelligence"], "-2.0 -4.4 -5.4": ["selected"], "7.3 19.3 15.2": ["zone"], "4.8 10.2 3.7": ["buildings"], "15.5 8.8 2.8": ["industrial"], "9.5 -8.6 1.9": ["contracts"], "4.8 14.1 3.9": ["advance"], "5.0 0.6 3.4": ["fit"], "-6.0 1.5 7.9": ["assists"], "-2.1 0.3 7.6": ["tickets"], "-0.2 2.7 5.7": ["youth"], "9.5 4.8 11.0": ["variety"], "3.9 7.7 5.3": ["matches"], "-1.0 20.4 6.7": ["defensive"], "13.4 -5.8 5.2": ["package"], "-2.5 2.8 3.6": ["requirements"], "4.8 0.1 -2.3": ["connection"], "-2.6 2.8 2.3": ["writing"], "7.7 2.6 7.2": ["ongoing"], "-11.8 5.0 6.0": ["explained"], "4.8 4.8 -0.4": ["accept"], "13.3 7.2 -1.0": ["lawsuit"], "6.1 -2.1 -4.9": ["profile"], "10.0 4.9 15.0": ["ending"], "3.4 -2.7 2.2": ["expenses"], "12.9 14.3 9.1": ["employee"], "2.1 5.5 6.0": ["resident"], "2.7 13.1 6.0": ["myself"], "5.2 10.7 14.3": ["stuff"], "13.5 19.0 6.1": ["standing"], "12.1 2.2 13.0": ["covered"], "1.6 15.3 10.8": ["politics"], "-3.8 6.9 -1.3": ["aware"], "11.3 7.1 1.0": ["device"], "18.5 6.1 1.7": ["display"], "15.1 11.6 9.5": ["culture"], "1.5 8.9 2.5": ["train"], "4.0 2.7 -0.1": ["driven"], "9.4 8.3 3.1": ["closer"], "12.9 14.4 8.7": ["illegal"], "4.1 10.2 10.9": ["meant"], "7.5 5.1 -2.1": ["technologies"], "3.1 3.9 12.1": ["card"], "6.3 18.8 24.0": ["dog"], "6.3 9.8 3.3": ["enter"], "0.9 14.4 0.3": ["communications"], "-3.9 36.6 11.3": ["weapons"], "4.1 -0.7 0.2": ["gained"], "0.2 -3.7 -2.5": ["supported"], "8.8 16.1 11.9": ["eye"], "5.9 1.3 1.1": ["associated"], "-5.2 11.4 5.4": ["chances"], "12.9 1.2 1.7": ["centers"], "6.0 27.0 -0.9": ["dangerous"], "3.9 6.4 3.4": ["views"], "-1.0 14.1 5.6": ["worse"], "5.3 -6.5 -0.4": ["studies"], "-6.3 -0.0 3.2": ["discussion"], "-10.0 -11.5 -2.9": ["attended"], "2.6 6.7 8.3": ["pace"], "-6.1 10.5 4.5": ["album"], "17.5 7.1 4.1": ["entertainment"], "-2.0 13.8 2.4": ["camp"], "2.1 12.5 3.0": ["trust"], "11.2 21.8 0.6": ["strategic"], "18.9 9.8 11.9": ["falling"], "4.8 2.7 2.5": ["favor"], "3.6 1.2 0.2": ["retired"], "8.4 1.4 4.2": ["removed"], "5.7 40.8 5.3": ["army"], "-1.1 10.2 8.6": ["balance"], "3.2 16.4 3.7": ["plane"], "1.6 11.0 1.8": ["quarterback"], "17.9 6.6 4.4": ["banking"], "13.4 2.4 9.7": ["baby"], "10.5 5.4 14.8": ["truck"], "-0.9 3.0 -1.1": ["sought"], "-2.4 -0.3 0.4": ["write"], "10.9 -0.0 -7.5": ["partnership"], "15.4 7.8 4.7": ["nearby"], "17.3 13.5 1.7": ["image"], "14.2 6.9 3.8": ["stars"], "2.6 2.7 0.9": ["volume"], "6.4 8.4 5.5": ["effects"], "4.7 0.9 -7.0": ["tests"], "10.4 19.7 -0.3": ["interests"], "-3.0 5.6 4.1": ["occurred"], "0.0 -2.5 6.2": ["bond"], "3.6 -4.5 -0.6": ["introduced"], "3.7 9.3 16.1": ["sport"], "4.0 4.3 0.9": ["spokeswoman"], "5.6 7.6 7.3": ["behavior"], "0.5 23.0 0.2": ["defeat"], "-1.4 4.4 -1.5": ["treated"], "3.2 9.0 1.0": ["direction"], "24.9 7.8 10.4": ["bigger"], "9.0 14.8 13.6": ["crew"], "11.6 3.7 0.9": ["allegedly"], "12.5 6.1 3.5": ["uses"], "1.6 5.0 14.3": ["mortgage"], "0.4 5.0 9.4": ["miss"], "6.8 10.4 20.4": ["catch"], "4.4 0.3 2.7": ["appearance"], "5.7 5.4 1.6": ["welcome"], "-5.5 4.0 1.9": ["experienced"], "-3.0 11.8 5.8": ["ideas"], "0.6 6.6 -2.5": ["negotiations"], "0.6 10.2 4.2": ["authority"], "7.9 0.9 13.0": ["slightly"], "3.6 0.3 -0.6": ["urged"], "14.1 13.8 7.4": ["hole"], "5.1 3.2 4.9": ["reform"], "-3.0 11.7 4.6": ["achieve"], "4.6 2.3 2.4": ["assistance", "phospholipase"], "4.7 1.3 -3.2": ["delivered"], "9.5 5.3 2.5": ["compete"], "8.3 4.3 1.3": ["link"], "-0.6 10.6 4.2": ["choose"], "1.5 17.1 3.6": ["possibility"], "8.7 -2.7 -0.6": ["ruled"], "4.5 4.4 0.4": ["interesting"], "1.8 5.2 5.6": ["seats"], "9.6 1.7 5.8": ["threw"], "4.1 3.3 4.7": ["drove"], "3.5 9.1 3.6": ["immediate"], "5.2 4.2 2.5": ["investments"], "3.8 -4.1 3.6": ["payments"], "7.9 7.1 11.7": ["northern"], "4.6 11.3 -0.9": ["relations"], "12.7 -4.0 13.1": ["license"], "10.6 -0.8 1.8": ["discovered"], "3.6 5.6 1.5": ["prove"], "-1.7 0.5 -1.2": ["registered"], "-1.2 0.9 0.5": ["perform"], "12.0 12.1 5.8": ["governments"], "7.6 -0.6 -0.7": ["debut"], "17.1 -1.8 7.9": ["researchers"], "4.9 2.7 6.4": ["accounts"], "2.4 4.4 11.3": ["limit"], "9.7 18.9 10.7": ["eyes"], "1.9 11.7 0.1": ["deaths"], "1.7 8.0 6.8": ["neighborhood"], "3.4 0.7 6.1": ["handed"], "6.9 6.9 4.2": ["veteran"], "5.3 7.8 0.9": ["alternative"], "10.7 11.3 9.0": ["basic"], "2.4 2.3 3.1": ["manage"], "6.5 10.4 7.8": ["tools"], "3.5 13.6 1.4": ["negative", "wing"], "2.3 5.2 0.7": ["secretary"], "3.8 29.9 8.4": ["kill"], "-4.6 3.2 1.8": ["receiving"], "3.2 -0.8 0.9": ["collection"], "-7.2 4.2 2.8": ["coaches"], "-3.1 7.9 6.0": ["returns"], "-2.5 1.8 3.5": ["surgery"], "-6.7 19.3 15.7": ["gun"], "9.1 3.7 1.4": ["replace"], "4.6 20.2 4.4": ["fan"], "8.3 3.9 2.6": ["institutions"], "1.1 20.8 2.0": ["personnel"], "2.1 3.1 7.9": ["golf"], "2.1 16.2 11.1": ["happens"], "8.7 13.3 6.2": ["surprise"], "7.1 12.2 5.5": ["changing"], "7.7 4.7 10.7": ["kick"], "4.3 5.1 1.1": ["ceremony"], "11.9 8.2 -2.8": ["west"], "1.3 5.6 -0.2": ["resolution"], "9.1 8.6 10.0": ["broken"], "10.0 5.1 2.2": ["plenty"], "8.8 11.1 4.4": ["nor"], "3.8 10.2 1.2": ["easier"], "0.9 14.7 3.5": ["passing"], "0.6 10.7 9.5": ["pain"], "6.4 7.0 11.0": ["bar"], "6.4 18.4 9.3": ["everybody"], "4.1 4.5 10.3": ["talent"], "3.8 3.5 -1.3": ["represent"], "6.1 16.5 12.0": ["unless"], "11.1 8.0 6.0": ["pull"], "4.1 5.6 11.9": ["cast"], "16.1 -0.4 -4.3": ["deals"], "2.3 3.4 -2.4": ["grade"], "-0.9 13.5 7.0": ["song"], "14.7 0.5 3.6": ["filled"], "0.6 16.5 9.8": ["wish"], "9.7 2.8 12.2": ["begins"], "0.7 2.3 6.5": ["affect"], "13.8 16.3 4.3": ["nations"], "4.9 -7.8 8.3": ["fee"], "12.3 5.7 3.5": ["largely"], "15.7 12.5 5.6": ["apparently"], "-3.2 11.5 7.2": ["email"], "2.1 -4.2 -3.1": ["portfolio"], "-2.2 -0.0 -5.7": ["recognized"], "-1.7 6.9 -1.1": ["speaking"], "9.1 5.5 1.3": ["shut"], "6.8 6.3 6.5": ["sit"], "23.3 1.7 3.2": ["profits"], "-2.7 7.4 4.7": ["reporting"], "8.9 -1.5 -0.1": ["holds"], "5.4 -0.0 -2.6": ["represents"], "10.4 -2.5 10.8": ["dozen"], "7.2 5.3 8.2": ["practices"], "3.2 11.3 3.8": ["declared"], "16.9 1.0 8.4": ["rich"], "9.8 -0.4 2.7": ["thanks"], "10.9 -1.6 6.0": ["supplies"], "1.3 5.6 3.8": ["convicted"], "6.3 4.6 7.1": ["native"], "-6.2 2.8 -0.5": ["improvement"], "23.1 -6.2 7.5": ["amid"], "0.8 -2.1 6.4": ["classes"], "-2.6 -7.6 3.1": ["participate"], "0.0 -4.4 1.1": ["accepted"], "15.8 6.3 9.3": ["jump"], "5.4 9.0 5.4": ["village"], "-0.2 23.9 7.0": ["aircraft"], "2.9 9.7 -2.5": ["poll"], "3.2 5.9 -5.7": ["abuse"], "16.0 4.7 2.1": ["carrying"], "12.5 7.6 0.6": ["east"], "2.2 7.9 1.3": ["pro"], "1.6 8.7 4.8": ["client"], "-2.5 9.2 1.9": ["equity"], "10.7 9.8 4.4": ["sitting"], "3.4 10.9 11.0": ["generally"], "-3.7 -4.2 2.8": ["notes"], "-2.3 6.6 4.5": ["unable"], "12.1 12.0 31.6": ["ice"], "7.2 6.6 9.8": ["houses"], "20.5 1.7 0.2": ["stake"], "5.3 11.0 12.5": ["rain"], "1.2 1.6 4.6": ["savings"], "17.5 9.8 1.7": ["warning"], "3.1 -0.6 2.7": ["brings"], "-5.9 -3.2 2.4": ["discussed"], "9.6 2.6 12.8": ["adults"], "-4.5 3.4 4.1": ["file"], "0.2 5.0 -0.7": ["responded"], "7.2 3.0 13.0": ["parking"], "-5.0 10.1 4.2": ["returning"], "7.0 10.0 10.4": ["orders"], "3.8 13.5 3.9": ["telling"], "3.2 0.9 0.4": ["encourage"], "0.8 10.5 2.5": ["identify"], "9.5 2.5 5.5": ["pushed"], "12.2 3.0 3.9": ["joint"], "0.9 8.8 -0.7": ["conduct"], "5.1 -4.9 9.6": ["suspended"], "14.8 15.1 7.2": ["wind"], "8.6 6.6 2.4": ["edge"], "-4.5 13.3 3.8": ["roads"], "1.4 4.0 7.2": ["female"], "-1.9 4.5 6.0": ["sentence"], "12.5 -2.8 -5.0": ["backed"], "7.0 -1.3 -5.4": ["promote"], "6.3 5.2 8.5": ["eighth"], "-0.4 10.2 2.4": ["influence"], "3.0 2.1 0.9": ["organized"], "7.8 21.3 15.0": ["cold"], "5.9 -2.5 6.6": ["bills"], "5.7 -1.4 4.9": ["payment"], "0.9 0.2 0.1": ["properties"], "16.9 3.9 5.1": ["scale"], "27.7 19.7 2.3": ["rival"], "-9.2 14.3 1.5": ["religious"], "-2.2 -0.4 8.4": ["retirement"], "9.0 13.3 9.5": ["possibly"], "17.3 4.8 1.3": ["turning"], "4.6 13.2 -0.5": ["civil"], "16.5 12.3 8.4": ["moves"], "3.5 16.7 8.9": ["currency"], "12.9 0.6 2.6": ["aimed"], "8.7 7.3 11.1": ["breaking"], "-6.8 1.6 8.0": ["alcohol"], "2.6 -4.7 7.8": ["awards"], "-3.3 1.0 -1.1": ["talked"], "3.5 -4.4 6.1": ["grant"], "18.1 15.8 4.1": ["wall"], "2.7 4.5 -5.8": ["allegations"], "4.8 7.1 4.3": ["requires"], "3.6 7.3 5.3": ["mayor"], "-2.9 4.9 16.5": ["races"], "10.5 4.8 7.3": ["struggling"], "5.8 21.9 11.1": ["whatever"], "1.2 7.3 0.9": ["readers"], "-0.8 -3.1 -6.2": ["appointed"], "-1.3 10.3 3.2": ["voting"], "2.8 1.6 0.1": ["significantly"], "4.8 13.3 7.9": ["heat", "supplicated"], "12.7 7.5 8.7": ["structure"], "-2.1 2.6 -3.8": ["transfer"], "1.5 4.7 -1.9": ["supporting"], "7.1 2.1 6.6": ["trend"], "12.9 10.9 2.0": ["increasingly"], "10.5 7.0 1.7": ["networks"], "1.2 14.0 10.7": ["otherwise"], "-0.6 17.7 -0.5": ["conflict"], "12.4 8.2 12.3": ["cutting"], "17.3 7.6 -1.2": ["modern"], "3.5 7.0 6.8": ["wearing"], "27.9 -0.2 1.4": ["executives"], "4.4 8.8 4.3": ["entry"], "3.8 10.7 7.4": ["playoff"], "6.5 10.1 4.9": ["wireless"], "2.6 14.8 11.9": ["meaning"], "7.3 9.1 14.9": ["leg"], "3.9 7.7 7.2": ["intended"], "-0.4 8.7 4.9": ["appropriate"], "2.6 4.8 2.6": ["excellent"], "15.3 -7.8 3.9": ["involving"], "12.4 8.7 3.8": ["stood"], "15.8 7.2 9.8": ["heads"], "14.2 15.7 11.1": ["rescue"], "8.1 12.8 3.8": ["walking"], "7.0 10.2 1.9": ["locations"], "4.7 0.3 5.5": ["materials"], "10.5 10.9 1.9": ["sending"], "3.8 8.6 4.6": ["bodies"], "4.0 11.7 20.5": ["snow"], "11.2 9.9 63.0": ["fish"], "1.4 10.9 6.2": ["feels"], "-3.3 9.6 4.3": ["deputy"], "7.2 -1.7 6.6": ["mile"], "1.0 11.4 7.9": ["passengers"], "1.6 14.1 14.6": ["except"], "7.5 4.2 9.5": ["storage"], "13.7 3.0 11.8": ["shop"], "5.8 13.2 10.0": ["supposed"], "8.2 4.3 -1.2": ["numerous"], "-3.8 6.3 2.1": ["songs"], "2.9 -5.3 3.3": ["awarded"], "1.3 8.3 1.3": ["traded"], "5.6 6.2 6.1": ["sister"], "2.0 10.4 6.6": ["possession", "secretase"], "4.6 12.3 5.1": ["realize"], "-0.7 15.2 4.1": ["understanding"], "4.6 8.0 1.2": ["ten"], "4.8 14.0 1.6": ["justice"], "5.8 7.2 -3.6": ["rating"], "15.3 2.9 5.4": ["expensive"], "21.4 -0.5 6.1": ["jumped"], "-0.6 6.7 0.0": ["improving"], "16.2 1.9 2.5": ["fraud"], "5.0 13.2 25.2": ["animals"], "6.5 5.0 -8.7": ["dedicated"], "1.9 4.1 8.3": ["tight"], "7.2 5.1 2.5": ["lawyers"], "10.9 7.2 8.1": ["sets"], "9.7 -5.0 -3.1": ["linked"], "11.7 2.6 0.1": ["providers"], "2.7 4.5 1.6": ["investigators"], "18.9 7.9 2.9": ["stands"], "3.8 34.9 6.9": ["terrorism"], "23.6 9.8 9.8": ["arm"], "5.5 23.3 2.1": ["freedom"], "7.6 2.1 0.6": ["notice"], "4.7 -0.1 4.3": ["sentenced"], "5.3 25.5 1.2": ["coalition"], "5.6 10.9 9.6": ["touch"], "1.7 13.9 6.1": ["exercise"], "15.3 -0.9 2.7": ["settlement"], "11.3 14.2 14.4": ["disaster"], "-3.0 8.7 2.0": ["assist"], "16.3 0.2 2.8": ["electronic"], "-1.9 11.1 6.5": ["playoffs"], "9.3 11.5 8.2": ["combination"], "-1.1 0.4 7.9": ["apply"], "-2.1 6.7 0.2": ["shared"], "3.7 8.9 4.5": ["doctor"], "6.4 -1.3 -2.3": ["comprehensive"], "-2.0 -0.2 0.9": ["earn"], "7.8 0.8 3.7": ["fill"], "14.4 8.0 19.6": ["rock"], "100.0 4.5 11.8": ["giant"], "7.3 1.0 5.2": ["please"], "10.8 8.5 8.4": ["suit"], "18.3 -2.4 -2.6": ["owns"], "5.6 7.1 7.5": ["electricity"], "6.3 2.4 -2.3": ["exciting"], "4.7 5.9 3.4": ["winners"], "14.4 7.3 2.1": ["beating"], "11.9 4.1 5.4": ["protest"], "9.7 -8.7 -3.2": ["rejected"], "-2.5 6.2 10.9": ["ticket"], "0.9 8.4 21.0": ["farmers"], "4.4 5.3 8.4": ["ride"], "45.5 5.9 -1.5": ["maker"], "5.3 2.4 2.3": ["heading"], "9.0 2.6 9.9": ["regulations"], "11.0 -4.1 1.2": ["models"], "8.0 3.7 16.3": ["ends"], "10.5 3.1 -4.0": ["innovative"], "2.5 -1.3 3.3": ["upcoming"], "-1.1 9.8 3.9": ["writer"], "-2.4 -2.8 -1.5": ["performed"], "-2.1 4.3 3.9": ["films"], "4.6 24.0 14.8": ["arms"], "-6.1 9.6 3.1": ["married"], "9.0 8.7 7.1": ["prosecutors"], "1.5 12.2 0.7": ["agents"], "8.0 1.7 3.5": ["handle"], "-8.9 13.1 -0.4": ["duty"], "3.2 15.1 7.2": ["captain"], "-2.1 8.7 7.7": ["securities"], "-0.8 2.8 7.2": ["employment"], "0.1 5.5 2.7": ["surprised"], "1.2 4.2 8.9": ["worried"], "3.3 2.6 7.3": ["ninth"], "2.6 0.8 2.0": ["pointed"], "11.0 6.0 2.6": ["magazine"], "8.8 9.3 7.2": ["threatened"], "19.8 5.1 -0.6": ["headquarters"], "2.8 -2.1 10.3": ["participants"], "-4.0 10.4 0.0": ["visiting"], "7.3 14.5 14.3": ["fly"], "5.8 3.9 1.1": ["primarily"], "-3.5 5.3 4.8": ["respectively"], "2.6 6.8 14.3": ["transportation"], "-8.0 1.6 8.8": ["younger"], "6.1 3.1 2.5": ["jury"], "0.2 11.9 -4.4": ["respond"], "-2.1 3.3 3.1": ["rural"], "-3.4 6.3 -0.2": ["acting"], "-2.2 14.4 3.3": ["factor"], "6.5 5.5 -0.7": ["update"], "9.4 14.2 26.2": ["island"], "21.2 6.1 9.7": ["flat"], "12.4 8.6 6.2": ["remove"], "5.3 3.9 5.9": ["photo"], "-0.4 -1.0 2.4": ["selection"], "10.7 -0.8 5.5": ["scheme"], "12.9 2.3 -0.2": ["impressive"], "4.5 12.5 4.9": ["becomes"], "1.7 1.0 -3.0": ["indicated"], "2.7 4.6 -2.2": ["photos"], "6.9 -2.7 -4.6": ["professionals"], "0.8 3.3 4.1": ["fewer"], "9.9 0.9 5.4": ["shopping"], "5.4 7.4 7.7": ["split"], "8.0 6.1 -3.1": ["initiative"], "1.5 10.2 7.6": ["stretch"], "2.8 1.6 8.0": ["monthly"], "8.0 7.3 5.1": ["stronger"], "0.0 -0.7 0.6": ["bench"], "5.0 7.1 16.4": ["racing"], "1.1 4.7 1.3": ["none"], "-1.0 14.0 4.7": ["values"], "3.0 3.2 16.7": ["farm"], "16.3 5.2 1.1": ["producer"], "-5.0 3.8 4.4": ["reduction"], "18.8 6.3 8.8": ["famous"], "4.8 7.6 5.8": ["broadcast"], "12.4 1.5 2.1": ["promised"], "4.7 9.6 -3.7": ["operate"], "15.2 6.0 -6.9": ["acquired"], "4.4 6.1 7.1": ["goods"], "1.0 4.0 2.1": ["relatively"], "-0.6 8.8 9.5": ["passes"], "4.6 21.0 5.9": ["purpose"], "4.7 9.8 4.3": ["movies"], "7.3 -0.7 -2.0": ["directors"], "7.1 4.4 4.4": ["clubs"], "-1.6 12.8 8.7": ["conservative"], "4.4 4.5 -2.1": ["comfortable"], "7.1 1.8 2.2": ["replaced"], "-6.9 12.0 0.4": ["matters"], "3.4 8.7 2.7": ["hospitals"], "6.6 28.2 5.1": ["opponents"], "7.2 23.7 2.3": ["targets"], "-1.7 15.4 2.5": ["suffering"], "7.2 -0.0 14.5": ["festival"], "5.6 4.1 7.7": ["compensation"], "0.6 6.9 -0.7": ["guilty"], "5.5 7.4 -4.6": ["efficient"], "5.2 1.0 4.9": ["managers"], "9.9 13.5 5.9": ["truly"], "-0.4 19.6 2.3": ["faith"], "-5.1 7.3 0.3": ["scores"], "4.6 -0.0 -1.6": ["busy"], "7.3 -2.1 1.4": ["extend"], "6.6 5.0 5.1": ["faster"], "8.6 22.5 6.1": ["yourself"], "14.0 13.1 10.2": ["weak"], "10.0 3.3 8.2": ["rare"], "11.7 3.2 3.1": ["initially"], "2.2 7.8 0.6": ["importance"], "8.2 5.0 10.3": ["waste"], "5.6 12.8 1.1": ["suspected"], "1.6 8.0 -1.0": ["margin"], "12.1 5.0 4.5": ["watched"], "7.8 6.2 2.7": ["meters"], "14.9 13.5 8.2": ["franchise"], "3.8 3.4 5.3": ["fashion"], "21.1 2.3 19.8": ["pound"], "10.2 4.3 4.9": ["professor"], "18.1 -4.0 6.6": ["multi"], "9.9 -1.1 9.8": ["grown"], "5.7 7.1 8.6": ["estimate"], "-0.3 5.2 7.0": ["document"], "2.2 -0.6 6.1": ["register"], "10.6 5.7 17.4": ["cable"], "1.2 17.7 5.4": ["obviously"], "14.1 7.2 6.9": ["familiar"], "17.1 4.0 12.6": ["scientists"], "-2.9 1.4 7.7": ["artists"], "0.4 -1.1 0.9": ["invited"], "-1.7 17.6 -2.8": ["crimes"], "1.3 9.5 7.5": ["prepare"], "4.4 1.4 5.0": ["volunteers"], "9.8 10.6 11.5": ["cool"], "1.8 2.6 -2.4": ["financing"], "13.2 8.7 -0.7": ["images"], "6.5 6.7 10.1": ["fixed"], "10.0 -6.3 -0.6": ["hired"], "4.0 2.8 -5.4": ["enable"], "6.4 17.2 10.7": ["camera"], "-0.8 10.1 6.4": ["memory"], "10.4 7.5 5.8": ["historic"], "2.3 3.7 25.6": ["dinner"], "6.3 5.0 -1.9": ["proved"], "11.4 3.8 6.1": ["sees"], "2.6 12.4 2.6": ["telephone"], "9.9 15.8 2.1": ["vision"], "16.6 4.4 1.5": ["reportedly"], "6.4 3.5 2.0": ["soccer"], "14.4 19.9 22.6": ["ship"], "9.4 16.3 -0.0": ["path"], "1.1 9.7 4.3": ["actor"], "-8.6 12.1 1.7": ["circumstances"], "1.0 13.2 4.8": ["severe"], "10.5 6.4 2.3": ["expert"], "-4.3 9.0 -0.7": ["traveling"], "16.6 3.1 -0.2": ["engineering"], "11.0 7.1 12.8": ["dance"], "3.1 11.3 3.3": ["overseas"], "2.0 4.0 13.9": ["bridge"], "2.0 4.0 2.4": ["lowest"], "10.0 9.3 11.9": ["auto"], "0.7 9.5 8.3": ["counts"], "3.7 12.0 4.5": ["attempts"], "3.9 2.4 1.9": ["reflect"], "7.7 10.7 12.6": ["color"], "0.4 18.0 7.3": ["wounded"], "6.6 27.4 1.3": ["secret"], "-3.1 -0.1 -4.2": ["visited"], "13.7 18.5 2.5": ["greatest"], "3.0 11.4 10.0": ["leaves"], "8.7 12.4 9.8": ["types"], "7.2 -2.1 -5.5": ["representatives"], "1.9 11.5 8.1": ["worry"], "8.5 19.1 1.5": ["internal"], "-3.6 2.0 6.3": ["adds"], "-3.8 0.7 6.5": ["athletes"], "6.3 2.1 8.8": ["mix"], "24.6 6.4 5.3": ["industries"], "7.8 9.4 0.6": ["ministry"], "1.9 -2.6 -3.1": ["signing"], "2.8 6.0 -2.6": ["targeted"], "-1.4 10.5 1.5": ["tells"], "2.7 1.6 3.9": ["serves"], "-3.4 -1.4 0.3": ["graduate"], "-4.8 9.7 -0.7": ["quoted"], "0.3 1.4 -2.1": ["argued"], "4.8 -0.8 -4.1": ["association"], "7.1 4.9 5.8": ["lots"], "8.5 -2.1 -0.7": ["announce"], "12.1 6.8 -1.8": ["shortly"], "8.0 -8.8 1.2": ["featured"], "-4.0 6.1 11.3": ["marriage"], "8.1 0.9 2.7": ["contained"], "-5.1 18.3 -0.4": ["priority"], "4.3 41.1 2.6": ["terrorist"], "9.3 7.0 6.2": ["unlikely"], "7.6 12.7 8.5": ["causing"], "-3.6 4.0 -2.9": ["directed"], "7.2 6.5 -1.4": ["code"], "5.0 16.5 5.4": ["die"], "3.5 6.5 2.0": ["category"], "2.4 0.7 -3.2": ["chosen"], "4.0 7.6 6.1": ["shift"], "1.7 0.1 1.6": ["maintenance"], "-0.1 6.9 7.2": ["apartment"], "4.0 8.1 2.8": ["theater"], "4.4 15.4 6.4": ["effectively"], "2.6 15.0 12.7": ["mine"], "-2.7 5.3 2.8": ["upset"], "10.2 6.5 0.6": ["western"], "12.3 -2.6 5.1": ["nationwide"], "1.4 11.1 7.8": ["thinks"], "9.0 7.3 10.5": ["euro"], "8.1 -0.9 2.1": ["closely"], "15.9 13.6 3.0": ["friendly"], "6.4 7.0 11.5": ["channel"], "5.0 15.5 7.1": ["brain"], "-2.7 4.1 1.7": ["custody"], "11.6 2.4 18.3": ["barrel"], "5.6 4.2 5.1": ["afford"], "1.5 18.3 19.0": ["dogs"], "-4.2 -0.4 3.5": ["residential"], "8.6 12.3 5.9": ["dream"], "8.3 17.0 9.9": ["actual"], "8.8 7.7 3.6": ["reaching"], "7.3 7.4 -1.9": ["transaction"], "4.6 3.3 3.1": ["finals"], "5.8 10.3 -1.5": ["cooperation"], "1.8 14.2 32.4": ["boat"], "6.0 -2.8 -4.9": ["investigating"], "-5.5 20.4 -1.2": ["communication"], "-7.6 5.3 7.2": ["freshman"], "11.8 1.1 8.1": ["outlook"], "4.2 5.9 0.8": ["deadline"], "14.7 13.6 13.2": ["surface"], "16.6 5.0 3.0": ["parent"], "11.5 5.9 3.8": ["phase"], "9.3 12.0 26.1": ["eat"], "-4.7 14.3 9.6": ["asset"], "1.3 30.0 1.6": ["truth"], "4.8 1.2 5.2": ["delay"], "4.3 1.5 7.0": ["enjoyed"], "13.9 9.9 8.4": ["shape"], "2.0 6.5 7.2": ["anticipated"], "6.0 -2.8 -2.5": ["representing"], "9.3 0.3 -3.3": ["purchased"], "2.2 -2.0 5.5": ["hoped"], "7.2 5.2 10.7": ["portion"], "6.2 10.2 -0.9": ["opposed"], "7.9 9.2 5.8": ["enterprise"], "6.4 12.9 25.7": ["animal"], "15.9 11.7 2.5": ["controlled"], "8.2 11.1 7.3": ["politicians"], "3.6 1.8 9.6": ["cards"], "6.9 2.4 3.9": ["suggest"], "3.6 -1.0 4.2": ["concert"], "6.5 6.8 9.5": ["uncertainties"], "-2.2 -0.2 0.7": ["granted"], "10.6 10.9 10.3": ["beautiful", "ole"], "2.5 9.1 -2.7": ["recognize"], "4.5 3.0 -3.8": ["joining"], "-4.0 7.9 10.1": ["flights"], "1.7 17.5 10.5": ["absolutely"], "-0.9 11.4 5.1": ["dealing"], "8.2 0.9 14.0": ["cap"], "14.2 9.3 4.8": ["turns"], "8.4 4.5 0.2": ["ties"], "-9.7 3.6 -3.0": ["informed"], "6.2 8.1 6.5": ["window"], "4.7 3.3 9.0": ["pool"], "-4.9 1.9 4.4": ["coaching"], "2.2 0.3 0.5": ["titles"], "19.5 13.1 20.7": ["blue"], "12.0 11.1 4.4": ["amazing"], "9.7 10.6 9.2": ["fears"], "3.5 5.7 3.3": ["demands"], "-1.1 -3.6 0.1": ["cited"], "1.8 -3.1 -6.1": ["behalf"], "2.2 -1.4 5.6": ["bonds"], "8.9 9.0 9.4": ["shoulder"], "5.8 8.8 2.5": ["seriously"], "-4.4 7.6 9.3": ["districts"], "10.3 18.7 9.0": ["aggressive"], "1.4 10.5 3.3": ["alive"], "9.1 19.8 0.0": ["bomb"], "1.6 19.3 6.5": ["suspects"], "15.9 16.1 7.0": ["dark"], "16.1 19.4 38.5": ["sea"], "1.4 16.0 3.9": ["therefore"], "-5.9 2.3 6.8": ["overtime"], "0.0 -4.9 -0.5": ["submitted"], "-1.3 14.0 5.5": ["agenda"], "2.8 6.0 2.6": ["establish"], "7.7 13.5 5.4": ["engine"], "12.5 2.8 3.5": ["mainly"], "0.8 5.0 2.2": ["maximum"], "4.0 3.4 16.6": ["male"], "12.7 5.9 7.7": ["pushing"], "9.2 10.8 6.8": ["airline"], "0.0 1.1 2.3": ["principal"], "7.0 2.3 0.4": ["library"], "4.7 4.4 13.1": ["pieces"], "9.9 -3.7 -0.6": ["dispute"], "4.4 14.0 8.0": ["corruption"], "-2.9 10.1 3.5": ["reserve"], "20.1 -8.4 -0.7": ["sponsored"], "7.0 37.0 0.5": ["militants"], "2.8 10.3 3.4": ["reducing", "judicature"], "9.1 -2.8 -1.5": ["originally"], "8.0 7.1 -0.1": ["sharing"], "10.0 -0.8 10.2": ["mixed"], "2.6 10.4 -0.1": ["complaint"], "5.7 4.8 9.9": ["realized"], "7.5 10.4 2.4": ["crucial"], "0.9 4.6 10.6": ["province"], "8.5 12.5 7.6": ["ultimately"], "9.2 7.7 -4.8": ["brands"], "8.3 16.6 0.5": ["capabilities"], "3.9 6.1 0.6": ["acknowledged"], "5.7 15.0 2.2": ["distance"], "0.9 22.0 5.0": ["struggle"], "11.5 7.8 -2.0": ["stations"], "0.3 -1.3 -4.3": ["discussions"], "1.4 -1.7 8.3": ["judges"], "7.7 4.7 -2.4": ["extensive"], "21.0 7.0 1.8": ["manufacturers"], "-4.4 7.5 -0.3": ["achieved"], "-4.7 14.8 -3.4": ["defeated"], "2.1 26.8 2.7": ["assault"], "21.1 -0.1 9.0": ["worker"], "2.7 14.3 -1.0": ["criticism"], "5.6 1.3 14.8": ["usual"], "3.3 -5.4 5.5": ["presentation"], "-3.8 -3.2 -6.6": ["improvements"], "-1.3 -3.0 -2.8": ["represented"], "3.4 -2.3 -0.1": ["findings"], "-2.5 3.3 15.9": ["counties"], "9.9 7.1 3.4": ["stolen"], "6.7 5.9 1.5": ["expense"], "2.9 6.9 0.3": ["editor"], "1.6 9.1 1.7": ["herself"], "2.4 2.1 -2.7": ["complaints"], "6.4 4.5 4.9": ["buyers"], "-3.4 4.1 -3.6": ["mentioned"], "-2.3 3.7 0.7": ["stayed"], "3.5 10.5 -4.8": ["efficiency"], "4.4 18.6 8.3": ["democracy"], "2.6 3.9 11.7": ["knee"], "3.5 2.8 -3.6": ["connected"], "6.9 37.2 6.0": ["terror"], "10.3 -0.5 -3.6": ["operates"], "8.5 20.0 9.5": ["neighbors"], "9.3 5.8 -1.2": ["successfully"], "7.5 1.1 2.4": ["permanent"], "4.5 10.2 5.7": ["parliament"], "6.4 1.3 12.4": ["adult"], "2.6 0.6 9.5": ["ages"], "-5.2 5.2 3.5": ["consistent"], "7.7 1.3 4.0": ["proposals"], "3.6 5.5 9.0": ["explain"], "9.2 3.9 2.1": ["formed"], "5.3 -0.4 6.1": ["weekly"], "-0.5 -2.8 -2.8": ["supports"], "15.5 7.5 23.9": ["coast"], "12.5 4.2 5.2": ["broad"], "-5.0 3.7 -4.3": ["relevant"], "3.1 10.7 6.5": ["opener"], "7.3 2.4 5.9": ["detailed"], "1.1 0.6 -2.4": ["letters"], "5.9 17.3 13.4": ["guess", "endosymbiosis"], "12.7 6.3 1.1": ["internet"], "5.4 3.2 3.8": ["struggled"], "3.6 9.3 3.3": ["entering"], "14.5 5.1 1.7": ["widely"], "1.1 4.7 6.4": ["recovered"], "-1.4 7.3 4.9": ["happening"], "-1.1 3.8 -0.9": ["par"], "9.3 2.3 4.8": ["protests"], "0.4 11.3 9.2": ["colleagues"], "7.3 17.8 6.0": ["tool"], "5.0 14.8 14.8": ["trees"], "3.9 8.1 6.0": ["text"], "9.6 16.8 -1.7": ["capable"], "3.8 -3.3 -3.3": ["monitoring"], "3.3 6.9 10.1": ["limits"], "-8.0 -1.2 2.9": ["eligible"], "-1.7 13.7 8.5": ["passenger"], "11.3 -0.6 -0.8": ["expanded"], "8.0 6.8 3.3": ["reputation"], "2.8 3.6 5.8": ["brief"], "6.5 10.0 6.5": ["motion"], "5.9 11.5 6.1": ["treat"], "1.1 18.4 -1.6": ["fought"], "-1.5 -1.9 2.5": ["concluded"], "-2.4 4.8 3.9": ["gap"], "-0.1 6.0 8.9": ["unemployment"], "5.9 3.0 23.4": ["restaurants"], "14.2 9.7 6.1": ["ad"], "7.8 0.5 3.9": ["surrounding"], "11.8 0.5 3.2": ["stepped"], "4.5 -0.9 1.4": ["drew"], "-1.1 -2.0 7.4": ["collected"], "16.3 6.0 5.3": ["retailers"], "8.9 8.9 6.7": ["preparing"], "-4.1 8.8 1.8": ["wear"], "6.1 20.4 4.1": ["destroyed"], "3.2 27.2 0.0": ["threats"], "11.4 0.1 0.1": ["invest"], "10.2 10.5 -1.2": ["concept"], "0.8 -1.4 2.4": ["recommended"], "12.4 19.6 1.9": ["flying"], "2.8 -0.2 8.7": ["minimum"], "3.9 7.7 3.7": ["flow"], "0.8 -0.6 5.5": ["resulted"], "11.1 2.9 0.9": ["marked"], "27.4 4.7 10.2": ["chain"], "-2.2 38.1 7.7": ["combat"], "0.3 4.0 9.4": ["rookie"], "7.1 1.8 9.8": ["noon"], "-3.1 -0.7 7.5": ["performances", "hypnotherapists"], "5.5 -3.9 -7.6": ["founded"], "6.3 8.0 10.2": ["artist"], "2.8 17.9 4.8": ["reporter"], "5.6 3.6 -0.9": ["celebrate"], "14.7 -6.0 6.1": ["featuring"], "5.5 -1.5 2.7": ["gathered"], "12.2 11.5 4.9": ["potentially"], "8.0 14.4 -2.3": ["publicly"], "1.3 0.1 5.9": ["disappointed"], "9.6 8.4 -4.1": ["pictures"], "-6.4 8.6 3.7": ["touchdowns"], "16.3 11.5 9.8": ["fallen"], "4.0 9.2 7.3": ["depth"], "13.1 -3.0 12.9": ["auction"], "7.6 4.8 6.7": ["wonderful"], "4.6 2.6 -2.6": ["criticized"], "8.2 19.8 -5.5": ["attacked"], "3.2 15.9 2.2": ["essential"], "3.9 7.8 3.9": ["damaged"], "-12.1 -3.3 -2.7": ["qualified"], "9.9 -0.7 -0.1": ["banned"], "3.8 4.5 2.8": ["suggests"], "4.8 2.7 -1.7": ["specifically"], "7.6 0.1 3.5": ["sat"], "8.2 15.6 7.6": ["loved"], "18.4 4.2 6.5": ["dozens"], "3.6 5.2 -2.9": ["representative"], "3.3 5.3 12.7": ["typically"], "11.0 10.4 1.0": ["era"], "6.1 1.4 -0.1": ["singer"], "5.1 18.5 3.7": ["thus"], "10.5 4.4 1.7": ["creation"], "-3.6 5.4 4.2": ["teaching"], "4.0 3.3 8.0": ["acres"], "-0.3 5.7 0.4": ["challenging"], "-2.9 1.6 1.5": ["encouraged"], "-4.3 -0.6 8.6": ["seniors"], "12.4 8.3 5.7": ["quarters"], "7.7 1.9 5.9": ["momentum"], "9.7 8.5 1.3": ["producing"], "14.1 -2.1 6.7": ["processing"], "7.6 6.7 11.3": ["inches"], "13.1 1.7 2.4": ["segment"], "10.4 7.4 7.4": ["versus"], "10.9 8.4 11.3": ["mining"], "3.9 11.7 3.9": ["route"], "3.4 2.8 -0.7": ["expertise"], "-0.6 7.4 6.2": ["touchdown"], "10.7 5.1 2.4": ["promise"], "10.4 5.7 2.5": ["healthcare"], "12.3 11.4 13.7": ["yen"], "16.1 3.8 -4.8": ["integrated"], "2.8 9.1 3.2": ["neither"], "7.6 6.7 5.2": ["puts"], "8.7 6.0 8.2": ["foundation"], "6.0 10.0 5.0": ["overnight"], "9.0 31.2 5.2": ["armed"], "5.3 10.4 3.2": ["ex"], "1.2 7.4 5.9": ["outcome"], "4.7 15.5 4.2": ["reaction"], "11.8 1.8 5.8": ["producers"], "6.1 0.4 3.3": ["follows"], "18.4 6.7 3.5": ["fields"], "13.2 6.1 4.8": ["stadium"], "10.5 6.3 2.9": ["failing"], "6.7 2.3 9.5": ["aside"], "10.1 8.4 11.4": ["bed"], "4.4 11.6 -1.0": ["doors"], "7.1 7.2 6.0": ["pilot"], "13.6 3.9 5.3": ["operators"], "11.0 7.3 6.0": ["forms"], "4.7 -0.5 -3.2": ["extension"], "19.1 6.4 5.4": ["mass"], "13.6 4.8 -0.2": ["substantial"], "-5.9 6.4 -3.1": ["obtained"], "-1.5 1.6 2.9": ["adopted"], "1.3 8.5 -0.4": ["reserves"], "2.4 -2.3 2.1": ["carries"], "-3.9 12.7 -3.1": ["trained"], "13.0 5.0 1.6": ["contain"], "5.1 7.4 10.4": ["tackle"], "10.3 -2.1 8.8": ["temporary"], "3.1 6.7 -4.6": ["proven"], "10.8 6.4 6.8": ["regulatory"], "-1.0 18.1 2.0": ["violent"], "-2.5 28.3 -0.6": ["danger"], "7.5 15.3 19.2": ["tree"], "19.7 13.1 3.9": ["boss"], "2.0 13.9 1.0": ["apart"], "6.4 9.3 6.7": ["gift"], "1.1 5.7 8.6": ["musical"], "4.6 9.3 11.5": ["warm"], "-0.4 7.5 6.0": ["creative"], "11.7 10.0 6.1": ["transport"], "9.1 5.7 1.6": ["developers"], "11.0 12.8 7.3": ["likes"], "9.1 7.6 3.6": ["courts"], "12.0 3.4 8.2": ["wake"], "5.0 23.4 4.0": ["shoot"], "3.0 1.6 4.4": ["lineup"], "10.1 -0.1 7.6": ["regulation"], "12.4 14.7 12.3": ["kid"], "5.5 24.6 -1.2": ["task"], "0.4 2.0 5.3": ["blog"], "5.5 -8.0 1.0": ["hosted"], "11.6 6.6 8.0": ["eastern"], "6.5 6.8 5.3": ["drawn"], "4.6 22.4 1.2": ["regime"], "1.8 -1.7 6.8": ["pending"], "7.2 23.3 5.4": ["ourselves"], "9.8 15.6 1.2": ["threatening"], "2.8 23.8 5.0": ["mistake"], "9.0 3.2 10.9": ["laid"], "1.6 16.8 1.9": ["journalists"], "4.8 3.9 10.4": ["cultural"], "3.8 13.0 7.7": ["blame"], "-2.9 5.7 2.9": ["copy"], "22.9 17.0 12.8": ["machine"], "5.0 3.5 10.5": ["mail"], "5.0 4.2 10.4": ["proper"], "-4.5 7.0 -4.3": ["listen"], "5.3 4.7 -0.6": ["links"], "-2.9 5.2 3.3": ["relationships"], "11.3 2.3 1.2": ["premium"], "-5.6 10.3 2.8": ["assessment"], "12.6 -2.5 -0.9": ["generated"], "1.7 -0.1 0.9": ["chose"], "2.4 15.5 -2.1": ["captured"], "14.8 3.3 7.7": ["summit"], "10.3 6.1 10.2": ["climate"], "-4.2 4.9 4.9": ["sophomore"], "3.0 10.3 1.3": ["keeps"], "-0.5 16.5 6.7": ["teammates"], "2.8 -4.5 -2.0": ["dismissed"], "4.9 -0.2 0.9": ["generate"], "3.0 5.5 12.4": ["hockey"], "6.2 11.0 1.3": ["vital"], "10.0 22.7 10.6": ["territory"], "6.5 6.0 4.0": ["elsewhere"], "-0.0 1.7 17.9": ["hair"], "2.2 6.5 10.1": ["resulting"], "2.0 13.5 10.3": ["veterans"], "2.2 3.4 -0.9": ["recognition"], "9.6 7.9 2.8": ["accounting"], "-5.5 13.9 2.9": ["polls"], "12.3 11.5 6.1": ["holes"], "3.9 1.4 0.3": ["initiatives"], "2.1 4.0 5.6": ["amounts"], "3.5 4.8 6.0": ["finishing"], "7.8 2.6 8.8": ["length"], "0.4 4.0 2.8": ["birth"], "23.2 21.7 6.1": ["rivals"], "0.1 11.2 8.9": ["gay"], "18.1 1.0 10.3": ["roughly"], "-1.0 5.5 0.9": ["performing"], "1.4 3.9 6.9": ["futures"], "13.4 7.8 11.6": ["exports"], "0.7 5.3 -4.8": ["tested"], "5.7 12.6 12.2": ["seed"], "15.5 14.2 -0.6": ["blow"], "0.2 8.5 9.4": ["historical"], "2.7 10.3 4.2": ["starter", "gutsful"], "-2.2 9.2 10.1": ["guests"], "3.4 9.7 21.6": ["river"], "5.4 1.9 2.8": ["minor"], "18.8 2.0 14.0": ["pop"], "8.0 4.6 6.0": ["predicted"], "23.5 3.7 13.8": ["roll"], "4.4 12.2 -0.0": ["acts"], "1.4 6.0 2.0": ["recalled"], "7.0 21.9 5.9": ["anybody"], "1.0 14.0 11.9": ["strategies"], "15.9 9.7 10.2": ["sharp"], "2.9 11.6 19.0": ["horse"], "9.3 6.3 10.4": ["prize"], "2.2 7.8 -0.3": ["valuable"], "4.9 15.5 6.5": ["witness"], "-3.9 4.9 10.0": ["drinking"], "-0.1 -2.2 6.3": ["contribute"], "8.4 6.7 -0.5": ["computers"], "3.7 -2.7 4.4": ["guidelines"], "10.9 -3.8 -0.7": ["funded"], "5.9 -4.0 4.4": ["delayed"], "6.7 -0.1 3.3": ["handling"], "11.3 4.8 -2.3": ["exclusive"], "12.9 18.2 5.0": ["repeatedly"], "-4.4 1.1 5.7": ["academic"], "0.2 8.0 8.1": ["resource"], "11.3 4.9 3.1": ["output"], "-0.2 0.2 3.9": ["contributions"], "10.7 3.9 0.6": ["background"], "-5.7 9.4 3.8": ["runner"], "2.5 4.6 8.0": ["prospects"], "5.7 8.2 3.3": ["filing"], "-5.6 -3.7 -5.5": ["questioned"], "2.0 0.7 6.9": ["applied"], "5.7 5.7 0.1": ["ratings"], "1.8 1.0 -3.3": ["thank"], "6.3 21.2 10.8": ["characters"], "-1.8 5.6 26.2": ["wine"], "8.8 13.1 -0.2": ["saving"], "17.7 4.2 14.5": ["lift"], "-1.6 37.2 8.4": ["civilians"], "7.1 9.2 3.2": ["identity"], "10.6 2.7 -3.3": ["ownership"], "8.7 16.6 1.9": ["obvious"], "14.1 11.3 10.7": ["throwing"], "10.6 -0.9 3.7": ["settle"], "5.7 0.9 6.9": ["tracks"], "14.4 9.2 2.4": ["smart"], "3.8 -1.3 -2.7": ["developments"], "2.4 4.4 24.6": ["lunch"], "5.5 0.8 5.6": ["bail"], "6.2 16.8 3.2": ["forget"], "0.3 2.9 1.1": ["transition"], "9.1 9.9 9.1": ["equal"], "8.9 -0.8 -4.3": ["founder"], "-0.9 0.6 -4.5": ["involvement"], "-0.2 7.9 7.0": ["gotten"], "16.3 13.9 8.0": ["protesters"], "17.6 0.2 1.0": ["euros"], "6.8 2.5 8.6": ["homer"], "1.5 38.6 5.9": ["opponent"], "5.1 3.2 3.8": ["competing"], "3.7 -1.9 3.4": ["submit"], "8.8 5.0 8.0": ["projected"], "1.3 16.2 4.8": ["cell"], "9.3 -1.5 -3.8": ["monitor"], "10.5 3.0 8.3": ["century"], "-4.0 -4.0 6.6": ["sessions"], "-0.2 -1.8 4.8": ["meets"], "17.9 -1.4 5.9": ["begun"], "14.2 4.3 21.9": ["metal"], "8.5 17.4 1.0": ["critics"], "5.5 -1.9 -0.3": ["forum"], "-1.4 2.6 -4.2": ["honored"], "0.2 7.7 6.4": ["ballot"], "1.6 2.6 -1.7": ["affairs"], "2.0 16.4 1.2": ["desire"], "7.0 -0.3 11.3": ["click"], "13.6 6.7 0.8": ["expanding"], "-6.2 10.2 2.8": ["topic"], "-4.6 -0.7 -0.9": ["recommendations"], "15.5 6.6 3.2": ["sectors"], "2.0 16.0 5.3": ["causes"], "7.9 1.2 9.4": ["ease"], "9.8 0.7 -2.3": ["marks"], "5.0 2.0 5.8": ["consumption"], "-7.6 -4.1 -2.1": ["appointment"], "10.7 11.0 -1.0": ["officially"], "-3.1 15.7 3.7": ["argument"], "16.1 6.3 -4.0": ["newly"], "6.5 9.8 6.3": ["wonder"], "5.8 16.1 5.8": ["spirit"], "11.4 7.8 7.2": ["ring"], "8.8 8.4 8.1": ["employers"], "4.2 1.2 -2.5": ["strongly"], "3.1 -0.9 7.1": ["registration"], "0.4 3.8 10.4": ["gasoline"], "-6.3 1.2 8.0": ["salary"], "16.3 3.0 6.1": ["blocks"], "18.0 10.4 14.6": ["classic"], "1.9 -0.5 0.9": ["educational"], "11.3 2.9 20.2": ["feed"], "-0.5 7.2 0.7": ["managing"], "3.5 16.8 7.9": ["cells"], "11.7 13.1 16.5": ["stick"], "6.2 10.1 10.3": ["exploration"], "10.4 3.9 -3.3": ["installed"], "6.7 5.3 5.2": ["blamed"], "4.4 6.5 5.0": ["insisted"], "-3.4 13.4 2.1": ["conversation"], "4.0 3.1 6.1": ["trends"], "6.5 22.2 5.2": ["elements"], "1.1 0.8 3.1": ["guidance"], "7.1 3.5 2.4": ["charity"], "11.6 1.0 -3.1": ["emerged"], "6.0 2.5 3.0": ["blocked"], "5.7 1.7 5.1": ["replacement"], "9.0 2.2 9.1": ["covering"], "8.8 17.2 -1.5": ["powers"], "3.4 1.2 14.1": ["tourism"], "1.5 3.7 -1.4": ["enhance"], "24.5 7.8 1.6": ["operator"], "6.6 11.5 1.8": ["saved"], "6.5 4.2 21.3": ["plate"], "3.9 10.9 0.2": ["engaged"], "1.8 4.5 7.9": ["expecting"], "1.7 12.9 -0.8": ["ranks"], "4.1 -0.3 3.6": ["donations"], "5.0 7.5 0.5": ["mention"], "-3.2 6.5 10.8": ["immigration"], "6.6 3.7 14.4": ["pension"], "7.9 8.1 1.1": ["emerging"], "0.6 15.9 5.6": ["moments"], "-4.8 6.9 0.5": ["testimony"], "1.3 12.4 3.1": ["witnesses"], "5.4 19.9 6.3": ["impossible"], "5.7 12.1 5.5": ["tries"], "2.8 10.9 -0.1": ["rounds"], "6.6 2.6 -4.6": ["exposure"], "7.9 2.9 7.0": ["celebration"], "17.2 9.4 9.6": ["instance"], "13.9 -2.6 -3.2": ["controversial"], "-0.7 17.1 6.3": ["harder"], "0.2 10.0 4.7": ["stress"], "9.0 -4.4 6.6": ["settled"], "-3.2 5.4 2.1": ["remarks"], "-5.0 0.6 -1.2": ["articles"], "6.6 12.6 0.6": ["false"], "16.2 3.7 5.1": ["dominated"], "16.9 2.7 3.2": ["dramatic"], "21.3 4.6 7.1": ["collapse"], "3.7 10.2 6.1": ["attempted"], "1.3 1.2 4.1": ["drama"], "11.9 2.3 12.1": ["boards"], "12.2 8.5 10.5": ["museum"], "4.4 -5.7 0.3": ["attract"], "14.8 8.7 -0.3": ["remote"], "-4.3 7.5 -1.0": ["experiences"], "9.5 0.8 6.4": ["chair"], "6.5 14.2 1.6": ["anywhere"], "4.4 6.0 -6.1": ["messages"], "17.2 3.2 -2.7": ["developer"], "17.4 6.0 2.3": ["ads"], "13.0 1.5 2.7": ["opens"], "5.5 2.7 -1.1": ["confirm"], "-2.1 3.2 1.7": ["requested"], "2.1 11.5 2.3": ["error"], "10.5 0.4 5.8": ["print"], "-2.2 10.7 3.4": ["pitcher"], "9.8 -0.0 2.5": ["contains"], "-5.6 4.1 4.5": ["decrease"], "-9.6 -3.8 0.1": ["attending"], "9.1 4.2 -3.9": ["integration"], "11.8 4.6 6.6": ["thrown"], "13.4 4.6 8.8": ["unusual"], "9.1 5.2 4.5": ["stability"], "29.2 6.6 1.9": ["makers"], "19.0 8.2 0.0": ["merger"], "17.9 6.1 20.7": ["steel"], "1.6 0.9 5.9": ["yield"], "9.2 9.0 3.4": ["knocked"], "22.2 12.9 14.3": ["square"], "14.8 8.5 19.2": ["glass"], "10.6 3.5 0.5": ["inspired"], "7.4 14.9 9.3": ["flag"], "-4.2 5.7 1.5": ["volunteer"], "0.6 11.1 50.6": ["fishing"], "11.8 7.5 8.3": ["activists"], "2.0 14.0 6.4": ["firefighters"], "15.1 6.2 1.3": ["alongside"], "5.8 20.0 3.8": ["aim"], "5.2 1.8 3.4": ["guarantee"], "-10.1 -0.2 2.4": ["clinical"], "10.6 4.2 -0.3": ["claiming"], "-8.9 8.1 -3.2": ["staying"], "12.3 6.1 -0.0": ["tremendous"], "3.6 4.3 2.1": ["contribution"], "6.1 50.1 1.4": ["terrorists"], "23.2 10.9 8.7": ["wave"], "15.0 10.0 8.2": ["electric"], "2.3 -0.3 5.3": ["restrictions"], "6.6 8.7 3.0": ["recall"], "-2.8 0.4 5.6": ["implementation"], "2.7 20.4 5.5": ["knowing"], "3.4 8.4 12.6": ["skin"], "14.8 7.1 5.6": ["utility"], "3.4 3.8 5.1": ["processes"], "3.9 5.0 -2.8": ["halftime"], "10.7 8.2 8.6": ["fix"], "21.0 4.7 5.5": ["quarterly"], "-4.7 11.0 1.6": ["emotional"], "-6.3 3.6 -5.0": ["maintained"], "11.0 13.0 3.8": ["counter"], "8.4 -3.1 4.8": ["annually"], "1.9 8.0 5.7": ["repair"], "-3.9 7.2 0.6": ["obtain"], "-2.3 8.2 -0.9": ["abroad"], "4.0 1.4 3.4": ["stable"], "8.2 5.9 7.5": ["regions"], "8.5 5.5 8.4": ["tradition"], "4.8 16.0 6.8": ["totally"], "0.7 5.9 3.5": ["opinions"], "5.9 4.6 4.9": ["hosts"], "6.2 -5.0 2.7": ["citing"], "4.6 -0.4 1.5": ["pitched"], "0.4 12.7 2.2": ["necessarily"], "3.8 10.2 0.4": ["beaten"], "2.0 2.4 9.9": ["reasonable"], "3.2 7.3 8.5": ["drink"], "-1.3 9.3 14.6": ["poverty"], "7.6 7.4 4.3": ["properly"], "8.9 23.5 7.6": ["somebody"], "-0.3 -9.6 6.0": ["canceled"], "12.6 7.2 5.6": ["sounds"], "4.7 11.5 12.8": ["sick"], "-0.9 1.1 1.4": ["saves"], "6.9 11.7 8.6": ["lucky"], "15.5 12.0 9.6": ["folks"], "3.5 27.9 -2.6": ["defend"], "10.3 6.5 7.1": ["lights"], "-0.3 7.9 3.0": ["minority"], "11.4 8.6 5.4": ["posting"], "-0.3 9.2 17.1": ["drilling"], "-5.7 7.0 2.4": ["differences"], "6.8 7.2 3.7": ["regularly"], "-2.8 -2.3 0.4": ["roster"], "5.1 4.5 0.5": ["bankruptcy"], "-1.3 -5.1 5.2": ["participation"], "5.4 4.6 -0.3": ["interim"], "9.7 8.1 1.9": ["controls"], "18.5 18.0 10.8": ["competitors"], "14.4 7.6 13.5": ["stuck"], "7.5 6.3 -3.4": ["delivering"], "2.9 8.5 9.7": ["viewers"], "8.4 -1.3 -4.3": ["agreements"], "-0.6 6.0 3.9": ["subscribers"], "3.3 14.9 7.7": ["smoke"], "-4.9 1.4 -1.3": ["compliance"], "-0.2 12.0 5.5": ["manner"], "9.3 9.8 9.9": ["trucks"], "4.2 17.4 5.2": ["yes"], "-1.0 16.2 -0.0": ["mistakes"], "6.9 -0.5 4.0": ["formal"], "11.4 12.9 6.9": ["investor"], "10.8 5.4 0.9": ["speculation"], "-5.9 2.0 -0.0": ["qualifying"], "1.5 5.2 1.2": ["attorneys"], "8.3 7.2 6.4": ["finds"], "5.8 6.9 -2.6": ["quiet"], "7.3 -0.4 -0.7": ["cleared"], "9.8 -1.0 15.4": ["bag"], "15.2 9.6 1.3": ["explosion"], "9.4 7.0 7.0": ["taxpayers"], "10.8 7.0 7.5": ["guide"], "-5.7 7.9 6.5": ["occur"], "3.8 1.0 -2.7": ["encouraging"], "1.7 7.8 9.9": ["highway"], "2.1 10.5 7.0": ["sleep"], "0.2 8.4 8.2": ["recover"], "-6.0 -0.0 -5.2": ["interviews"], "13.2 14.0 9.2": ["satellite"], "12.8 14.8 1.5": ["entirely"], "2.9 4.4 12.1": ["dry"], "1.5 -7.7 3.7": ["papers"], "6.1 39.2 5.8": ["soldier"], "8.3 -3.9 7.7": ["covers"], "8.2 9.3 4.2": ["exhibition"], "11.3 13.1 1.7": ["blast"], "7.2 11.9 -2.9": ["capture"], "8.2 6.3 -1.5": ["function"], "-4.5 0.4 -2.8": ["availability"], "-1.0 1.7 10.8": ["lending"], "5.3 0.8 10.9": ["peak"], "13.8 5.7 18.2": ["wild"], "-0.7 18.0 4.3": ["facts"], "-2.6 -0.3 3.6": ["procedures"], "4.3 5.7 0.1": ["lap"], "-0.7 3.7 -0.7": ["awareness"], "-0.8 5.5 -2.9": ["pursue"], "7.9 -2.4 3.2": ["edition"], "11.4 8.1 4.4": ["studio"], "2.1 14.1 4.1": ["correct"], "18.5 7.4 14.1": ["inch"], "5.9 8.5 6.9": ["switch"], "0.1 -4.2 5.6": ["participating"], "1.0 9.3 9.7": ["tend"], "13.6 6.9 1.7": ["champions"], "8.7 11.6 12.7": ["lay"], "3.5 13.7 5.1": ["purposes"], "7.4 9.9 3.5": ["departments"], "0.5 10.4 -0.7": ["ranking"], "-5.8 -2.2 -6.6": ["addressed"], "-0.8 9.0 5.9": ["perspective"], "8.0 7.7 6.0": ["components"], "7.1 1.9 -0.9": ["seized"], "-0.2 2.1 5.5": ["clothing"], "10.4 10.8 7.6": ["drawing"], "5.1 25.5 1.1": ["resistance"], "-1.8 12.2 5.5": ["choices"], "-4.9 8.0 0.5": ["recording"], "9.1 -0.3 1.5": ["demanding"], "1.4 12.3 9.1": ["urban"], "6.6 -1.5 5.2": ["pages"], "9.2 -7.1 2.5": ["doubled"], "-0.9 -2.5 6.2": ["suspension"], "30.7 4.0 -5.0": ["manufacturer"], "11.4 6.6 -1.6": ["innovation"], "26.3 1.1 6.3": ["climbed"], "6.9 10.3 25.1": ["port"], "-7.3 7.8 3.5": ["runners"], "7.5 15.0 7.9": ["brothers"], "-4.1 0.8 2.5": ["visits"], "-0.9 5.2 3.6": ["implement"], "-1.1 12.5 6.5": ["relatives"], "4.7 7.3 4.9": ["atmosphere", "autoupdate"], "1.9 10.4 7.5": ["defined"], "-5.2 3.3 5.3": ["absence"], "15.1 2.6 13.1": ["steady"], "9.1 8.6 3.9": ["branch"], "1.6 6.3 6.2": ["pitching"], "3.4 4.9 13.3": ["normally"], "5.6 7.7 6.3": ["gathering"], "4.8 15.3 2.9": ["signal"], "-4.2 5.4 5.5": ["administrative"], "11.0 11.1 7.8": ["empty"], "0.2 9.2 -3.0": ["obligation"], "-9.4 31.1 4.5": ["commander"], "10.4 -6.6 5.8": ["prompted"], "11.4 7.1 9.1": ["falls"], "-2.6 8.2 1.8": ["taught"], "4.8 0.9 0.4": ["promotion"], "-0.8 7.6 -3.0": ["incidents"], "-1.9 16.3 -0.8": ["operational"], "8.4 0.9 6.2": ["pricing"], "8.3 4.6 16.1": ["silver"], "30.5 3.7 -9.2": ["subsidiary"], "-6.1 -2.9 1.6": ["qualify"], "1.9 23.5 3.7": ["escape"], "4.8 7.5 8.3": ["wealth"], "-10.0 10.3 2.8": ["singles"], "7.8 6.8 7.1": ["roof"], "0.6 21.0 7.4": ["extent"], "7.6 7.1 0.3": ["privacy"], "5.8 10.8 7.8": ["spots"], "4.9 4.1 6.3": ["tennis"], "0.3 -5.7 8.7": ["grants"], "2.5 2.1 -3.1": ["transactions"], "6.7 5.4 11.6": ["scientific"], "8.7 12.9 15.1": ["export"], "-0.4 9.4 6.3": ["referring"], "14.2 2.9 -0.4": ["preliminary"], "6.3 3.3 3.7": ["rooms"], "4.8 8.4 2.3": ["sanctions"], "3.1 5.0 0.4": ["degrees"], "14.7 10.8 26.9": ["eating"], "-0.4 6.8 13.2": ["legislative"], "-0.2 -3.8 9.8": ["resume"], "7.2 1.1 5.0": ["involve"], "8.1 8.4 0.1": ["resolve"], "11.1 3.8 -4.9": ["operated"], "-5.7 10.2 -2.2": ["sexual"], "6.5 14.4 5.8": ["prospect"], "14.1 -2.5 10.2": ["typical"], "0.2 3.0 3.0": ["membership"], "0.5 -1.0 9.7": ["hiring"], "-7.1 2.2 -0.4": ["consideration"], "-2.7 30.4 5.8": ["civilian"], "-3.0 9.7 9.2": ["fairly"], "5.9 1.4 -5.1": ["investigate"], "4.0 6.1 -4.4": ["violations"], "3.9 -1.8 -1.1": ["pipeline"], "5.9 3.4 -0.0": ["seeks"], "13.3 2.9 2.7": ["crore"], "3.7 -0.6 3.0": ["hire"], "8.6 7.9 4.0": ["theme"], "-5.3 4.6 0.3": ["stressed"], "3.4 6.5 9.7": ["resort"], "6.8 10.0 4.4": ["walks"], "0.1 3.2 -1.4": ["roles"], "7.3 4.0 16.3": ["rebound"], "0.8 10.3 -0.2": ["reference"], "16.5 3.0 0.3": ["specialist"], "1.4 7.3 10.0": ["timing"], "11.4 15.0 3.2": ["imagine"], "14.0 11.2 1.2": ["rapidly"], "6.7 15.7 9.7": ["angry"], "1.0 6.9 6.7": ["riding"], "-0.5 11.5 2.2": ["violation", "speculative"], "-0.8 14.6 7.1": ["attitude"], "-4.9 4.2 6.2": ["guest"], "2.2 3.2 1.6": ["select"], "19.4 3.7 9.5": ["tech"], "5.2 6.5 13.6": ["barrels"], "5.5 10.2 3.6": ["sensitive"], "9.8 -7.4 4.3": ["hosting"], "6.2 -1.5 2.7": ["demanded"], "-3.9 0.4 19.4": ["marijuana"], "6.4 14.0 3.5": ["intent"], "3.1 7.5 1.3": ["strengthen"], "1.8 5.9 7.3": ["channels"], "5.5 5.9 2.6": ["ministers"], "10.5 3.1 3.0": ["newspapers"], "1.4 2.1 -3.5": ["referred"], "-2.6 1.6 1.7": ["testified"], "3.9 7.3 7.8": ["column"], "-0.6 5.5 3.0": ["arrive"], "-3.2 4.8 -2.3": ["rushed"], "9.2 6.9 -0.5": ["kilometers"], "7.5 5.3 13.2": ["frame"], "6.1 1.0 -1.3": ["provision", "computerization"], "-2.6 11.2 -1.0": ["authorized"], "8.8 12.2 5.3": ["fail"], "5.4 1.8 0.9": ["completion"], "-4.2 4.5 -4.1": ["traveled"], "13.0 7.0 2.8": ["heavily"], "19.4 8.1 -6.3": ["acquire"], "10.4 6.4 1.9": ["striking"], "9.4 12.6 13.3": ["virus"], "3.3 -2.4 -6.4": ["secured"], "8.1 7.5 8.0": ["breaks"], "8.4 -0.6 0.7": ["attractive"], "11.8 20.2 2.1": ["indeed"], "4.9 -3.6 1.1": ["approve"], "2.3 13.5 8.4": ["survived"], "8.7 15.5 3.7": ["intense"], "5.6 2.9 9.5": ["somewhat"], "9.8 3.0 1.3": ["aims"], "9.5 11.4 7.1": ["crews"], "2.5 17.1 2.5": ["protected"], "-4.5 -7.6 0.8": ["checks"], "4.3 -0.1 -1.2": ["distributed"], "0.1 2.4 3.3": ["talented"], "11.7 -4.9 6.0": ["kicked"], "12.0 5.3 3.1": ["permission"], "1.5 10.8 1.4": ["judgment"], "9.1 11.1 23.0": ["beer"], "-2.6 2.1 3.4": ["clothes"], "4.6 8.8 15.6": ["coal"], "10.6 1.4 2.0": ["packed"], "7.3 -0.2 -8.4": ["promoting"], "6.0 7.5 6.3": ["flood"], "6.7 -1.1 -1.5": ["approached"], "5.6 8.6 6.5": ["towns"], "13.4 1.4 3.4": ["disappointing"], "2.1 2.2 -5.0": ["collaboration"], "-1.3 7.2 5.4": ["hopefully"], "-1.3 7.9 7.2": ["streak"], "7.3 16.1 18.8": ["balls"], "-2.6 11.4 1.4": ["sustained"], "3.3 -3.4 2.6": ["noticed"], "11.4 1.6 12.0": ["permit"], "6.3 8.8 27.7": ["beach"], "7.6 4.2 5.1": ["collect"], "5.3 7.7 3.0": ["journey"], "-4.4 4.8 0.7": ["victories"], "0.4 5.1 4.2": ["statistics"], "10.2 4.3 4.1": ["fantastic"], "3.4 8.2 12.0": ["rail"], "11.1 7.4 2.6": ["hundred"], "14.6 10.7 4.7": ["pack"], "5.6 3.8 10.9": ["broadband"], "2.8 2.8 8.0": ["cycle"], "2.0 -1.9 0.6": ["delays"], "-1.0 2.7 12.5": ["comedy"], "0.2 15.1 2.2": ["thoughts"], "11.9 7.7 6.5": ["hardware"], "10.0 3.6 2.4": ["solar"], "7.2 3.6 1.0": ["bound"], "4.7 -2.8 5.2": ["proceeds"], "-4.9 10.7 -0.7": ["suicide"], "0.8 22.7 9.1": ["prisoners"], "13.3 -0.8 1.4": ["discovery"], "12.3 10.5 8.7": ["dad"], "3.7 6.6 0.8": ["searching"], "10.1 5.8 4.4": ["longtime"], "18.4 -1.5 1.0": ["premier"], "2.1 24.1 4.6": ["command"], "1.3 3.1 -6.3": ["enables"], "13.2 -7.0 5.8": ["ranging"], "9.5 14.4 7.1": ["nobody"], "1.1 4.2 0.8": ["actress"], "2.8 3.0 2.5": ["aspects"], "1.4 14.8 5.9": ["fled"], "4.4 2.0 -0.2": ["videos"], "2.5 5.2 11.8": ["cricket"], "0.1 8.6 3.9": ["ratio"], "2.3 6.5 4.8": ["birthday"], "11.3 5.0 -1.6": ["restructuring"], "0.4 7.7 10.1": ["episode"], "4.7 9.8 6.3": ["cameras"], "-0.0 14.0 1.3": ["persons"], "3.8 3.7 7.0": ["championships"], "-1.4 7.1 -2.6": ["answers"], "9.0 3.9 1.6": ["promises"], "3.1 15.6 2.6": ["unknown"], "1.5 6.6 4.0": ["argue"], "15.1 5.1 5.4": ["surge"], "5.1 2.5 0.9": ["focusing"], "-2.4 7.3 3.2": ["doubles"], "14.7 -4.9 0.2": ["donated"], "3.4 5.5 1.8": ["ideal"], "23.9 3.7 4.2": ["equivalent"], "2.5 11.1 0.0": ["reliable"], "6.4 -1.4 11.2": ["sustainable"], "21.1 5.9 7.9": ["factory"], "2.9 12.1 4.2": ["scenes"], "5.2 17.1 11.0": ["survive"], "-3.7 -6.2 -7.0": ["contacted"], "2.1 8.8 2.8": ["mph"], "-8.7 8.8 3.3": ["residence"], "-2.6 3.0 7.4": ["trips"], "2.8 1.3 0.3": ["hotels"], "2.1 11.1 14.5": ["bat"], "-0.8 2.9 4.2": ["unclear"], "3.5 17.7 11.0": ["gang"], "9.4 1.2 7.2": ["grounds"], "19.2 4.7 9.0": ["slipped"], "18.0 18.1 6.7": ["carrier"], "5.2 17.8 8.7": ["bases"], "1.0 9.2 -1.1": ["prosecutor"], "3.5 5.2 3.0": ["categories"], "2.2 3.0 5.6": ["liked"], "1.9 14.3 3.0": ["accurate"], "0.8 -0.1 -3.1": ["advised"], "17.1 11.5 8.6": ["slowly"], "-5.1 7.9 11.1": ["abortion"], "9.3 6.8 12.3": ["mom"], "9.6 3.8 13.8": ["tons"], "0.6 3.1 4.2": ["requests"], "10.3 9.9 9.3": ["forcing"], "6.0 12.6 3.4": ["frequently"], "5.0 14.6 3.9": ["overcome"], "0.7 9.9 -4.2": ["inquiry"], "-6.4 18.1 3.5": ["situations"], "8.1 11.5 3.8": ["apparent"], "15.1 18.3 7.5": ["map"], "9.4 4.6 4.9": ["universities"], "16.1 12.6 21.9": ["bear"], "-0.1 8.3 -0.3": ["stroke"], "3.6 11.7 11.0": ["medicine"], "0.9 4.8 2.0": ["drives"], "0.6 -0.2 0.9": ["reforms"], "17.5 0.1 10.7": ["vendors"], "-1.2 20.0 -7.1": ["defending"], "-0.3 9.0 3.7": ["teach"], "9.8 8.6 7.8": ["medium"], "11.8 0.6 9.6": ["prime"], "12.5 19.0 13.3": ["basically"], "7.8 11.1 -1.5": ["exposed"], "-5.0 13.5 3.8": ["dialogue"], "4.4 -0.6 13.0": ["stimulus"], "14.1 2.9 -0.3": ["probe"], "4.2 13.8 10.6": ["methods"], "8.1 18.9 6.3": ["shall"], "16.0 5.3 5.4": ["landed"], "10.4 5.5 4.7": ["stages"], "5.7 5.1 -2.1": ["luxury"], "1.9 -1.4 8.8": ["dates"], "4.8 17.8 8.4": ["vulnerable"], "2.6 4.2 7.9": ["preparation"], "28.6 3.1 10.1": ["regulators"], "3.5 3.0 0.8": ["indicate"], "0.4 -4.8 -2.0": ["appearances", "assemby"], "13.6 8.4 3.7": ["theft"], "-0.5 6.6 -0.3": ["appreciate"], "1.3 -0.4 2.5": ["complained"], "14.0 16.1 5.7": ["chemical"], "2.4 10.3 6.9": ["relative"], "0.5 20.5 3.5": ["consequences"], "5.8 4.3 14.1": ["imposed"], "17.1 1.6 3.2": ["rolled"], "1.0 10.5 -0.4": ["alert"], "8.4 13.3 5.9": ["virtually"], "-2.7 2.9 9.4": ["provincial"], "14.4 8.3 7.3": ["forecasts"], "2.3 19.7 2.1": ["strikes"], "3.4 3.1 9.4": ["athletic"], "2.6 10.0 8.5": ["neck"], "6.0 7.6 17.2": ["tourists"], "3.0 7.0 6.2": ["sad"], "18.2 0.4 4.2": ["pct"], "15.0 -6.0 -4.9": ["prominent"], "8.9 42.3 12.2": ["allies"], "-5.9 7.0 1.0": ["writes"], "15.9 19.9 1.7": ["alliance"], "8.8 13.8 11.6": ["method"], "17.7 8.5 6.6": ["meanwhile"], "8.1 2.9 16.2": ["crude"], "-1.5 12.2 3.1": ["suffer"], "-1.5 0.4 -2.9": ["files"], "7.7 3.4 -0.4": ["quit"], "-4.1 14.6 -1.7": ["deployed"], "8.9 12.3 1.1": ["shock"], "5.8 4.6 9.2": ["picking"], "9.7 3.0 5.3": ["clock"], "10.0 6.2 0.5": ["posts"], "-1.7 9.0 2.7": ["regard"], "7.9 0.4 9.1": ["convention"], "2.8 5.5 5.9": ["penalties"], "12.9 0.1 -0.8": ["backing"], "14.1 8.7 2.3": ["rapid"], "9.1 8.5 -1.9": ["independence"], "-1.2 7.0 -0.5": ["novel"], "14.4 -1.7 0.8": ["scandal"], "2.8 8.8 0.6": ["campaigns"], "13.1 5.1 2.6": ["widespread"], "8.2 16.8 37.2": ["species"], "-5.5 7.9 -3.0": ["audio"], "-7.7 4.9 5.7": ["explains"], "8.2 4.8 2.8": ["investing"], "7.7 -2.4 -4.7": ["welcomed"], "-1.7 5.1 4.7": ["detail"], "9.9 12.5 3.3": ["unions"], "-9.5 10.2 5.0": ["moderate"], "-5.4 25.3 4.2": ["religion"], "7.3 7.9 10.6": ["earthquake"], "0.8 9.2 14.4": ["wedding"], "10.8 0.2 4.2": ["grabbed"], "4.9 6.2 4.5": ["restore"], "5.6 17.2 -2.6": ["plot"], "18.9 -1.6 15.0": ["lifted"], "7.3 8.1 17.1": ["coffee"], "13.5 16.7 11.6": ["sun"], "-3.2 18.6 7.3": ["honest"], "6.3 12.2 1.6": ["passion"], "-2.7 7.9 7.6": ["periods"], "2.1 4.4 2.1": ["publication"], "10.9 9.4 12.9": ["swing"], "1.3 9.2 4.8": ["toll"], "12.1 16.7 13.2": ["master"], "2.4 12.3 -2.7": ["useful"], "5.7 13.9 2.6": ["eliminate"], "-0.8 3.5 -4.2": ["answered"], "8.3 14.6 10.2": ["congressional"], "12.4 23.5 11.5": ["neighbor"], "15.7 8.9 11.3": ["dropping", "galloping"], "-0.8 41.8 12.6": ["weapon"], "14.7 -5.4 1.7": ["promising"], "-2.9 10.9 0.1": ["maintaining"], "6.2 14.5 7.4": ["seeded"], "6.1 11.1 6.8": ["arrival"], "15.8 12.4 17.5": ["soft"], "3.7 1.5 1.3": ["format"], "-3.3 3.1 -0.6": ["honors"], "17.0 5.9 3.1": ["trillion"], "9.2 1.6 10.7": ["teen"], "2.4 11.2 14.8": ["smoking"], "1.0 -5.3 -4.2": ["impressed"], "16.2 -0.5 1.1": ["consultant"], "36.7 5.4 10.9": ["tiny"], "1.8 6.7 7.5": ["temperatures"], "9.0 6.7 5.6": ["adviser"], "5.7 6.8 3.9": ["windows"], "4.0 9.8 8.3": ["shelter"], "15.3 24.4 2.2": ["deadly"], "8.3 3.9 -0.5": ["label"], "-3.7 1.6 5.7": ["noting"], "-3.4 5.4 7.4": ["foul"], "1.2 3.0 -2.6": ["commissioner"], "0.1 11.3 11.3": ["sheriff"], "0.3 14.0 1.5": ["succeed"], "-6.3 7.0 2.8": ["nomination"], "8.9 6.2 -2.6": ["upgrade"], "0.5 7.4 4.5": ["rely"], "18.4 0.4 2.5": ["string"], "4.4 8.2 1.8": ["trail"], "0.3 -6.3 6.5": ["aged"], "8.3 6.8 7.3": ["traders"], "7.8 -2.8 6.1": ["triple"], "-3.1 12.0 0.3": ["personally"], "-3.2 -1.6 2.8": ["implemented"], "4.9 9.9 3.5": ["preferred"], "6.4 13.3 6.8": ["winds"], "11.0 19.0 1.1": ["lies"], "4.9 12.5 -0.4": ["exist"], "10.8 5.8 2.2": ["proof"], "10.1 16.3 10.9": ["tank"], "0.1 13.4 2.6": ["zero"], "-0.1 4.8 4.9": ["secondary"], "-0.5 12.6 2.9": ["consistently"], "4.3 -1.4 0.1": ["delighted"], "0.0 14.3 -0.5": ["defender"], "19.5 17.9 7.8": ["suddenly"], "10.3 10.1 19.2": ["garden"], "5.7 -0.5 3.4": ["e"], "2.5 6.5 7.8": ["routine"], "5.3 10.2 6.9": ["anonymity"], "-0.3 9.1 14.2": ["postseason"], "4.6 -2.1 -0.1": ["introduce"], "8.5 3.7 6.0": ["venue"], "1.3 3.5 10.6": ["teens"], "0.5 -0.2 -2.1": ["affordable"], "2.4 3.9 43.1": ["meat"], "-0.3 -1.9 -4.7": ["resigned"], "-10.2 0.2 3.7": ["attendance"], "17.6 10.7 6.8": ["suppliers"], "10.6 7.4 16.2": ["concrete"], "-3.3 1.6 1.2": ["repeat"], "7.4 13.2 11.2": ["anyway"], "5.6 10.0 4.3": ["solve"], "1.4 4.5 3.6": ["convinced"], "8.5 13.3 13.0": ["legs"], "3.0 5.1 9.7": ["uncertainty"], "19.7 8.3 2.6": ["cheap"], "0.9 -3.7 2.0": ["programming"], "4.2 15.0 7.1": ["neighboring"], "6.7 22.2 10.4": ["helicopter"], "6.5 0.8 -7.3": ["demonstrated"], "15.6 1.5 7.1": ["bright"], "9.5 3.1 4.0": ["comeback"], "10.9 -1.6 3.4": ["offset"], "2.4 4.7 4.4": ["forth"], "-0.3 16.3 -0.0": ["harm"], "4.6 20.3 -2.3": ["protecting"], "-3.7 3.1 -0.1": ["detained"], "15.4 2.8 7.6": ["meter"], "-2.4 2.4 5.6": ["earning"], "0.7 6.1 3.6": ["glad"], "-5.2 7.0 1.4": ["duties"], "2.9 1.6 -6.7": ["rated"], "4.0 5.9 13.3": ["upper"], "15.8 8.1 13.5": ["dividend"], "10.3 15.3 5.6": ["senator"], "15.3 7.2 7.0": ["pulling"], "8.4 -5.2 10.0": ["organizers"], "8.1 12.4 1.6": ["exit"], "3.5 5.0 5.3": ["shoes"], "-5.3 0.7 1.2": ["entitled"], "5.9 7.9 0.5": ["viewed"], "1.5 11.0 2.3": ["clash"], "-0.7 -0.2 2.0": ["courses"], "-4.7 4.9 13.9": ["bike"], "-0.5 25.1 11.4": ["afraid"], "26.1 10.4 5.5": ["billions"], "11.0 9.8 6.6": ["hardly"], "4.2 2.3 -0.2": ["download"], "3.8 -4.9 -5.8": ["petition"], "7.6 5.7 11.6": ["bonus"], "2.5 17.5 5.5": ["lying"], "6.7 3.0 11.9": ["elderly"], "0.4 -0.0 1.3": ["reflects"], "6.8 28.1 7.3": ["hate"], "1.6 8.0 -2.5": ["errors"], "5.4 14.9 9.3": ["kinds"], "3.6 18.0 5.8": ["belief"], "-7.3 11.1 -1.1": ["assigned"], "11.9 10.5 11.5": ["crazy"], "4.4 1.4 8.8": ["arts"], "-3.1 4.4 -0.1": ["retain"], "16.7 4.8 5.4": ["longest"], "15.1 3.5 0.8": ["crashed"], "6.4 15.6 2.1": ["guards"], "5.8 11.4 2.4": ["assume"], "5.7 14.4 18.7": ["mouth"], "0.3 6.4 5.0": ["sufficient"], "14.2 5.2 5.8": ["barely"], "15.6 4.4 5.7": ["sharply"], "1.5 4.0 -5.6": ["connect"], "11.9 -3.8 6.7": ["offerings"], "-2.8 9.2 8.9": ["funeral"], "-0.6 0.6 -1.2": ["express"], "3.5 8.3 21.7": ["kitchen"], "6.5 1.2 0.8": ["purchases"], "1.1 -4.4 6.2": ["averaged"], "8.9 7.7 12.9": ["gaming"], "6.7 3.9 -3.1": ["disclosed"], "1.0 15.5 0.9": ["kills"], "-0.5 8.3 -3.2": ["investigations"], "-0.6 8.2 3.6": ["constitution"], "-5.4 5.0 -2.1": ["flexibility"], "10.3 11.5 -1.9": ["burning"], "3.0 16.3 1.9": ["extreme"], "0.5 6.8 -1.3": ["updated"], "17.7 8.7 2.4": ["unprecedented"], "7.5 10.0 8.4": ["dealers"], "15.1 7.1 -2.5": ["acquisitions"], "2.8 5.9 5.4": ["backup"], "-1.4 3.0 4.9": ["faculty"], "-2.9 12.5 1.6": ["prosecution"], "4.2 11.2 6.9": ["tired"], "13.8 7.1 8.2": ["ups"], "-2.1 -1.5 4.4": ["optimistic"], "12.9 2.1 -0.1": ["pledged"], "5.6 9.1 7.1": ["temperature"], "2.6 7.9 7.1": ["funny"], "8.1 4.9 8.0": ["handful"], "8.6 7.3 -1.3": ["targeting"], "15.0 1.8 5.1": ["broader"], "0.3 10.4 0.0": ["rape"], "6.9 17.9 2.4": ["intention"], "20.5 8.5 8.5": ["super"], "-2.5 14.6 10.4": ["regardless"], "-0.2 4.3 8.0": ["nights"], "14.5 9.5 3.1": ["abandoned"], "9.1 17.0 35.5": ["birds"], "17.8 -2.2 -0.8": ["sponsor"], "8.4 10.7 4.4": ["airlines"], "2.9 0.2 4.8": ["tips"], "-0.7 3.9 7.6": ["conviction"], "8.3 1.1 -2.3": ["celebrated"], "3.8 10.9 14.0": ["taste"], "8.6 -3.9 -2.1": ["relating"], "6.2 17.5 -1.0": ["citizen"], "5.7 6.0 4.8": ["locked"], "9.9 9.0 15.1": ["paint"], "9.3 5.4 7.7": ["load"], "15.6 15.9 12.0": ["essentially"], "-2.1 9.6 -0.1": ["symptoms"], "-3.4 6.4 17.3": ["horses"], "-3.8 -8.3 -1.4": ["reviewed"], "-2.2 23.0 11.2": ["guns"], "3.2 -7.2 2.6": ["handled"], "1.7 8.0 6.4": ["emissions"], "8.4 9.4 12.5": ["hurricane"], "14.0 18.2 8.1": ["walls"], "2.0 8.2 -5.2": ["counsel"], "1.0 7.2 7.9": ["consensus"], "8.1 6.6 2.4": ["reveal"], "12.9 18.0 3.9": ["everywhere"], "-1.2 9.4 7.1": ["occasion"], "8.1 6.7 8.9": ["carefully"], "5.9 10.5 2.6": ["understood"], "1.1 7.7 9.0": ["inventory"], "0.9 13.5 0.3": ["engage"], "11.5 -1.8 -1.4": ["lease"], "14.4 12.0 3.8": ["incredible"], "10.1 14.8 4.5": ["constant"], "2.2 10.7 6.9": ["sons"], "-0.2 7.2 0.4": ["compromise"], "14.2 3.5 10.1": ["shops"], "5.0 5.1 10.3": ["worries"], "5.6 -8.2 3.3": ["raises"], "4.1 13.7 6.1": ["opposite"], "-1.3 1.9 -3.3": ["fitness"], "4.1 -0.4 3.4": ["database"], "6.6 0.3 2.0": ["diverse"], "6.0 7.8 9.8": ["stops"], "6.1 10.1 -0.3": ["battery"], "10.7 4.7 10.0": ["parks"], "5.2 11.9 4.7": ["rush"], "0.8 11.0 3.7": ["burden"], "8.7 -2.7 -0.7": ["controversy"], "-3.0 7.2 1.4": ["departure"], "6.4 12.5 12.4": ["luck"], "11.8 35.5 4.7": ["rebels"], "1.7 7.6 0.8": ["repeated"], "10.8 3.5 6.3": ["involves"], "4.6 21.6 8.3": ["firing"], "16.0 1.0 0.0": ["troubled"], "6.5 1.7 8.1": ["benchmark"], "13.0 6.2 -1.0": ["backs"], "6.9 14.8 5.4": ["anymore"], "7.2 7.9 3.0": ["institution"], "4.8 1.5 0.1": ["keen"], "-2.1 38.3 3.4": ["fighters"], "9.5 -1.0 -1.9": ["rallied"], "4.2 7.4 3.1": ["contrast"], "9.3 -2.6 -0.6": ["invested"], "4.8 6.2 9.4": ["assembly"], "10.0 4.1 -0.3": ["intends"], "25.9 -1.2 19.2": ["plastic"], "3.9 6.1 -2.3": ["converted"], "0.2 6.5 14.3": ["depending"], "9.9 10.8 2.7": ["ordinary"], "-7.1 -3.6 -2.3": ["credits"], "-0.9 7.8 3.7": ["flooding"], "-4.8 10.9 7.7": ["actors"], "2.4 12.8 2.7": ["productivity"], "0.5 18.3 5.7": ["democratic"], "-5.5 0.8 -7.5": ["transferred"], "7.9 7.3 9.5": ["tip"], "16.8 2.9 -1.2": ["interactive"], "8.5 3.6 18.5": ["casino"], "11.0 8.2 13.7": ["basket"], "9.0 5.8 24.2": ["chip"], "11.6 12.3 13.1": ["bet"], "-5.6 8.5 7.0": ["writers"], "-0.3 7.9 5.4": ["execution"], "1.8 5.0 4.4": ["requirement"], "7.7 10.5 0.4": ["automatically"], "1.2 4.7 1.9": ["plea"], "4.0 3.5 6.9": ["i"], "17.8 2.8 9.5": ["machines"], "16.0 -4.5 8.8": ["modest"], "-3.8 -1.4 4.6": ["procedure"], "2.0 5.5 7.1": ["calm"], "1.4 1.6 -0.3": ["updates"], "26.3 -5.1 -1.6": ["unveiled"], "9.3 7.0 -3.8": ["swept"], "9.2 8.8 12.4": ["loose"], "5.7 14.8 11.2": ["latter"], "1.9 7.7 2.0": ["nervous", "countered"], "3.3 8.9 14.0": ["agriculture"], "15.5 -1.9 4.5": ["valued"], "-1.0 5.4 4.8": ["pregnant"], "0.2 5.1 1.8": ["conclusion"], "3.0 8.4 11.4": ["homeowners"], "7.6 5.0 8.4": ["household"], "3.6 8.5 5.2": ["prefer"], "-3.7 10.3 5.1": ["enforcement", "intestate"], "7.8 1.1 4.2": ["requiring"], "0.2 7.7 3.9": ["definition"], "9.2 3.4 -2.7": ["demonstrate"], "10.0 9.3 7.8": ["parade"], "7.9 32.8 4.5": ["hero"], "2.2 1.6 3.9": ["economists"], "3.2 10.5 0.8": ["rushing"], "10.1 1.6 3.5": ["explore"], "0.6 -0.1 4.2": ["decreased"], "-2.6 27.5 5.6": ["patrol"], "10.0 5.5 -0.3": ["surprising"], "3.1 3.5 13.3": ["diabetes"], "6.9 10.3 5.8": ["component"], "5.4 12.3 10.7": ["anger"], "3.6 0.0 1.2": ["incentives"], "14.7 15.6 6.3": ["carriers"], "-8.1 -3.6 -2.4": ["commented"], "1.1 16.2 5.1": ["teammate"], "7.5 5.8 2.8": ["legacy"], "8.1 12.8 19.6": ["fleet"], "14.4 0.1 16.3": ["fat"], "1.2 -1.8 3.9": ["presents"], "-13.1 1.5 8.4": ["vacation"], "2.2 -1.4 2.5": ["introduction"], "10.7 -1.0 0.5": ["discount"], "1.3 -1.6 1.6": ["provisions"], "1.1 1.9 -7.3": ["praised"], "1.5 7.7 8.5": ["lane"], "17.2 -3.3 2.9": ["sells"], "7.0 2.8 -0.8": ["enhanced"], "5.9 48.3 5.4": ["insurgents"], "-5.6 3.0 -1.0": ["copies"], "10.1 9.7 6.0": ["pride"], "-1.2 17.1 6.0": ["odds"], "3.7 5.1 0.6": ["employed"], "-1.2 4.6 0.4": ["challenged"], "4.2 8.2 3.2": ["singing"], "-0.2 13.7 10.3": ["equally"], "18.1 -1.6 4.5": ["collapsed"], "14.3 7.0 3.5": ["thousand"], "11.3 13.4 11.3": ["landing"], "3.8 12.5 10.7": ["techniques"], "0.1 11.3 14.7": ["item"], "-3.8 27.3 3.0": ["objective"], "6.3 10.9 9.7": ["robbery"], "5.2 24.0 5.3": ["planes"], "26.4 10.6 2.2": ["supplier"], "6.1 7.5 2.1": ["comparison"], "1.5 2.5 5.1": ["gifts"], "14.0 2.1 -1.5": ["engineers"], "7.4 8.8 -0.7": ["burned"], "-6.1 2.1 2.6": ["arrests"], "-3.3 5.1 -0.9": ["feedback"], "10.2 -2.9 6.6": ["bags"], "5.7 4.8 1.8": ["revised"], "11.0 -3.5 3.5": ["versions"], "-1.7 6.9 11.8": ["agricultural"], "12.2 10.3 1.4": ["extraordinary"], "14.0 24.1 15.9": ["sight"], "-2.8 7.4 4.4": ["recruiting"], "6.3 27.0 -2.1": ["attacking"], "0.8 9.1 7.4": ["describe"], "30.7 8.5 -0.8": ["retailer"], "3.3 2.4 5.6": ["reflected"], "8.3 18.8 2.2": ["conspiracy"], "3.6 -1.7 10.6": ["calendar"], "4.2 5.6 6.7": ["creates"], "-0.4 14.8 2.8": ["minds"], "9.2 6.8 7.4": ["midnight"], "7.0 1.9 -0.9": ["functions"], "19.8 9.5 4.1": ["virtual"], "-0.0 -0.6 -2.4": ["delivers"], "-5.4 0.2 -0.4": ["resignation"], "8.2 12.3 7.7": ["badly"], "1.0 13.9 1.5": ["indication"], "-2.0 10.1 1.9": ["commit"], "0.5 5.5 11.6": ["pitches"], "4.4 3.7 11.4": ["gallon"], "16.9 17.4 6.8": ["ultimate"], "14.3 7.8 8.9": ["beauty"], "-5.4 3.9 -6.1": ["spoken"], "7.8 27.5 5.8": ["invasion"], "4.8 19.9 2.4": ["fires"], "1.9 -0.6 -2.9": ["concerning"], "9.2 11.5 34.8": ["waters"], "-6.0 -1.2 3.7": ["authors"], "-0.8 7.3 21.9": ["tea"], "-0.3 11.0 5.4": ["turnovers"], "9.7 -3.1 2.0": ["advisory"], "3.8 13.0 4.0": ["buried"], "4.2 0.6 6.0": ["rent"], "-3.3 -1.8 10.5": ["probation"], "6.0 6.8 6.5": ["excess"], "9.1 14.6 6.8": ["girlfriend"], "4.0 11.3 6.8": ["striker"], "-0.5 1.4 7.8": ["colleges"], "7.0 -4.2 4.4": ["priced"], "13.5 5.3 4.4": ["fastest"], "17.0 -5.2 4.0": ["robust"], "11.9 10.3 4.0": ["tracking"], "-3.1 -8.6 2.3": ["participated"], "5.6 26.0 7.8": ["lie"], "0.9 5.1 5.3": ["dating"], "10.9 0.8 20.7": ["bowl"], "10.0 -2.6 7.0": ["highlight"], "2.6 1.9 5.2": ["guaranteed"], "-1.1 9.4 1.7": ["chapter"], "3.4 3.1 8.9": ["tape"], "5.8 9.2 16.0": ["server"], "-4.6 14.9 4.9": ["deployment"], "14.1 13.8 3.7": ["shareholder"], "31.8 14.8 4.7": ["enormous"], "2.2 3.6 16.0": ["homeless"], "-4.0 11.9 6.7": ["illness"], "14.9 0.1 6.2": ["hall"], "10.0 3.5 5.4": ["exhibit"], "3.8 21.9 13.3": ["soil"], "3.8 7.0 3.7": ["noise"], "4.9 3.9 9.8": ["outs"], "-0.8 10.1 -1.1": ["deserve"], "23.0 4.7 9.5": ["rolling"], "3.9 13.7 7.1": ["rarely"], "-0.2 -5.7 0.8": ["adoption"], "4.3 12.8 5.7": ["peaceful"], "18.3 -0.1 2.6": ["containing"], "-3.1 9.3 3.6": ["felony"], "3.1 17.1 1.1": ["elite"], "3.2 8.0 7.2": ["cabinet"], "13.6 -3.9 1.0": ["sponsors"], "10.2 8.3 6.6": ["economies"], "6.6 -0.3 7.5": ["hike"], "24.6 5.6 2.4": ["arena"], "1.2 6.5 10.0": ["solo"], "17.4 4.5 2.8": ["platforms"], "6.1 7.6 -4.1": ["liability"], "11.4 7.2 9.8": ["outdoor"], "8.9 13.4 6.2": ["somewhere"], "11.1 8.5 -2.3": ["displayed"], "2.0 7.6 8.5": ["divided"], "3.1 9.0 3.3": ["context"], "7.2 -1.9 3.6": ["clinic"], "1.9 -1.2 1.3": ["lifestyle"], "5.9 8.8 -0.8": ["flew"], "7.1 -1.4 4.5": ["de"], "-2.1 0.2 -0.5": ["screening"], "9.4 7.1 5.1": ["dramatically"], "1.7 10.8 7.6": ["classroom"], "12.8 10.2 7.7": ["contractors"], "7.8 10.7 1.3": ["fundamental"], "12.4 3.4 8.5": ["partly"], "-1.2 8.9 0.8": ["ensuring"], "1.3 5.0 2.6": ["tackles"], "23.0 5.6 17.4": ["slide"], "5.6 5.0 4.3": ["suggesting"], "2.9 16.2 4.1": ["ill"], "11.8 7.1 15.3": ["imports"], "10.5 -6.7 6.6": ["highlights"], "-1.2 3.3 -0.2": ["assured"], "16.8 11.5 6.5": ["bunch"], "11.3 24.7 4.0": ["constantly"], "-7.6 2.1 7.3": ["holidays"], "4.0 3.8 5.7": ["touched"], "8.4 14.1 6.1": ["attempting"], "9.5 11.1 -0.7": ["fate"], "-2.0 10.9 -5.1": ["listening"], "-1.2 5.3 13.2": ["legislators"], "13.6 2.7 10.2": ["decent"], "12.6 1.5 4.8": ["risen"], "14.0 2.4 5.0": ["hanging"], "-3.0 0.4 -0.5": ["certified"], "-11.0 -0.0 -5.7": ["nominated"], "1.7 6.0 3.2": ["lists"], "-0.4 0.8 6.5": ["averaging"], "4.8 8.3 1.7": ["lessons"], "0.6 0.0 4.0": ["closure"], "8.9 5.0 9.2": ["lifetime"], "16.7 1.1 3.4": ["wider"], "3.2 6.2 0.7": ["shocked"], "4.4 8.8 -0.4": ["destination"], "21.5 8.6 6.9": ["tens"], "1.4 2.3 3.6": ["recommendation"], "-2.0 -1.3 4.8": ["buses"], "-2.7 9.3 0.5": ["phones"], "11.6 1.9 8.6": ["acre"], "-9.6 2.7 4.7": ["observed"], "8.5 1.1 5.1": ["trials"], "2.3 3.7 10.7": ["subsequent"], "3.8 19.2 8.3": ["scenario"], "12.4 9.6 18.2": ["shipping"], "-2.3 18.2 10.0": ["liberal"], "15.2 -1.3 12.2": ["lab"], "6.8 6.9 19.2": ["pet"], "4.1 -1.5 24.0": ["milk"], "9.4 10.5 -2.9": ["rumors"], "1.3 0.0 6.0": ["municipal"], "-1.9 5.8 7.7": ["starters"], "6.7 20.0 -5.7": ["bombing"], "6.3 3.3 4.6": ["popularity"], "8.9 0.9 7.6": ["thirds"], "19.0 5.9 12.8": ["bailout"], "3.7 6.7 24.0": ["menu"], "0.0 7.7 5.7": ["asks"], "2.7 13.5 2.3": ["tragedy"], "10.8 -8.0 3.4": ["packages"], "-11.1 -6.2 -5.8": ["interviewed"], "13.5 -10.1 10.0": ["licenses"], "-1.1 11.8 2.8": ["memories"], "6.1 16.8 5.6": ["colors"], "7.1 -5.7 1.6": ["consulting"], "-6.1 7.4 1.0": ["constitutional"], "2.7 1.7 6.4": ["welfare"], "6.4 0.5 4.6": ["nonprofit"], "6.6 2.2 3.5": ["designs"], "7.7 0.5 -1.7": ["verdict"], "9.7 10.9 4.0": ["defendants"], "1.1 2.6 7.9": ["ankle"], "13.4 -9.0 1.9": ["sparked"], "14.0 0.5 0.1": ["remarkable"], "-0.6 1.4 6.3": ["accompanied"], "13.4 6.1 6.0": ["briefly"], "11.3 13.2 1.1": ["letting"], "4.6 10.1 2.1": ["receiver"], "-3.5 2.4 3.6": ["wore"], "8.9 6.8 1.8": ["dynamic"], "14.8 2.7 7.1": ["attached"], "1.5 6.0 7.1": ["tone"], "10.6 10.3 12.1": ["reverse"], "5.1 18.1 11.7": ["survival"], "10.3 11.2 13.6": ["establishment"], "-0.3 5.4 25.8": ["meal"], "2.3 10.5 6.3": ["reception"], "-3.2 -0.1 -10.2": ["promoted"], "5.0 10.6 0.3": ["memorial"], "-4.2 4.0 3.7": ["warrant"], "9.1 6.9 4.2": ["complicated"], "0.3 9.7 8.5": ["inmates"], "8.3 8.2 8.3": ["rough"], "10.6 24.1 12.5": ["earth"], "12.7 17.2 11.0": ["merely"], "-0.1 7.3 1.9": ["eliminated"], "3.7 15.6 7.1": ["smile"], "-0.4 -1.0 -1.8": ["checked"], "8.5 13.7 11.4": ["adjusted"], "5.9 9.7 -1.1": ["sweep"], "1.3 14.1 2.7": ["leverage"], "2.6 13.2 0.4": ["external"], "8.4 17.0 11.0": ["mountain"], "-1.9 8.0 -0.3": ["amendment"], "-0.1 8.2 -1.1": ["associate"], "2.7 9.6 4.4": ["preserve"], "5.7 -14.2 -4.5": ["attracted"], "6.2 15.4 4.5": ["defendant"], "3.1 10.9 9.3": ["sorry"], "0.8 4.6 4.3": ["recovering"], "0.4 13.0 9.9": ["subjects"], "-9.3 7.3 3.5": ["diagnosed"], "0.2 7.6 -5.4": ["enabling"], "6.1 10.0 4.9": ["legitimate"], "10.3 23.5 6.9": ["terrible"], "8.4 0.4 -1.5": ["studying"], "19.0 5.4 7.8": ["shed"], "-2.0 12.2 4.2": ["achievement"], "0.5 -2.9 3.9": ["delegation"], "16.8 9.2 0.5": ["launching"], "-2.0 4.0 13.1": ["dress"], "3.3 7.0 3.3": ["reward"], "2.4 -6.2 5.8": ["circuit"], "18.3 -1.7 6.7": ["boxes"], "31.2 11.0 2.2": ["vast"], "2.2 2.0 3.9": ["adopt"], "2.7 10.6 2.9": ["affair"], "17.1 0.3 -8.3": ["formerly"], "4.7 5.7 8.9": ["enjoying"], "5.4 6.6 6.1": ["predict"], "-7.5 10.9 6.7": ["respective"], "0.5 0.3 4.7": ["recommend"], "5.6 -0.8 14.2": ["permits"], "9.9 12.0 13.2": ["pattern"], "-0.7 3.5 2.0": ["admits"], "8.5 -4.2 -0.4": ["renewed"], "-4.0 -1.0 4.8": ["satisfied"], "0.9 17.4 5.0": ["principles"], "0.0 8.8 5.7": ["crossed"], "1.0 9.6 2.2": ["travelers"], "23.7 6.5 7.9": ["landscape"], "1.9 3.0 10.3": ["deposits"], "4.3 9.5 12.9": ["aboard"], "9.8 12.7 3.0": ["narrow"], "-2.8 5.5 0.4": ["practical"], "13.1 4.2 3.0": ["installation"], "3.7 -5.2 10.5": ["samples"], "-1.6 7.4 7.2": ["exception"], "12.8 1.7 11.6": ["halt"], "15.1 5.2 4.5": ["loaded"], "-5.5 6.0 17.5": ["vaccine"], "13.9 8.2 10.3": ["cup"], "10.8 1.3 1.3": ["websites"], "7.9 -1.8 -2.1": ["urging"], "5.5 5.8 0.0": ["unlike"], "7.8 6.5 1.7": ["purchasing"], "11.1 8.3 9.8": ["sudden"], "13.2 -4.6 3.3": ["lined"], "4.9 1.5 16.4": ["tonnes"], "6.4 7.4 24.3": ["wood"], "5.6 8.1 6.4": ["eager"], "18.5 7.9 11.4": ["climb"], "2.3 12.1 5.1": ["careful"], "4.5 22.5 12.4": ["mode"], "4.5 100.0 9.7": ["enemy"], "3.6 9.2 6.0": ["wanting"], "19.2 5.8 -3.4": ["engineer"], "7.7 13.3 7.5": ["desperate"], "1.2 1.1 4.8": ["commissioners"], "23.7 5.0 -5.7": ["powered"], "-2.4 6.6 0.6": ["dealt"], "16.5 3.7 2.6": ["oldest"], "0.6 6.0 8.1": ["admission"], "0.8 2.6 0.7": ["connections"], "0.3 4.8 -0.1": ["therapy"], "-3.0 2.4 1.0": ["topics"], "1.6 16.2 -1.4": ["comfort"], "10.0 4.5 7.9": ["hang"], "-4.2 1.3 -4.9": ["addressing"], "7.1 4.3 8.5": ["celebrity"], "4.2 14.8 8.3": ["theory"], "-3.1 -0.7 -4.8": ["singled"], "11.7 0.3 1.7": ["donation"], "8.4 6.0 11.9": ["listing"], "-1.3 11.8 9.3": ["depends"], "0.3 3.9 -6.9": ["audit"], "12.2 14.9 6.6": ["employer"], "24.8 10.4 3.9": ["corporations"], "13.0 24.6 25.1": ["ships"], "23.8 -5.7 13.2": ["boom"], "3.4 16.5 -1.5": ["raid"], "2.6 28.0 4.0": ["innocent"], "7.4 6.7 4.7": ["fence"], "4.4 4.7 5.1": ["gather"], "9.6 4.5 9.3": ["bars"], "12.3 0.2 -0.1": ["stole"], "7.2 10.7 9.5": ["sentiment"], "12.1 1.7 0.8": ["cheaper"], "4.2 16.4 -0.4": ["journalist"], "3.8 1.8 7.3": ["rental"], "1.1 2.1 7.0": ["filings"], "-5.1 14.1 5.0": ["preseason"], "1.9 8.9 5.2": ["deeply"], "1.4 9.6 20.4": ["flu"], "23.1 -2.2 12.5": ["topped"], "3.9 -5.5 7.8": ["van"], "8.5 2.9 3.3": ["advocates"], "-2.1 4.6 -3.6": ["speaks"], "16.6 5.8 18.0": ["yellow"], "1.4 9.5 -3.2": ["accuracy"], "4.0 14.0 4.5": ["determination"], "31.4 11.1 2.9": ["takeover"], "13.3 16.3 9.3": ["loves"], "5.6 8.5 2.2": ["intend"], "19.0 3.1 4.1": ["grand"], "5.0 8.4 3.7": ["conducting"], "2.7 1.9 8.5": ["deposit"], "1.2 12.8 10.1": ["routes"], "-6.9 -1.7 -2.2": ["graduated"], "8.3 6.2 5.9": ["underlying"], "-1.2 11.1 5.6": ["neighborhoods"], "-3.4 21.8 7.6": ["objectives"], "13.8 2.9 2.8": ["spotted"], "-3.0 6.6 4.4": ["speaker"], "0.3 0.2 9.3": ["matched"], "15.8 0.6 5.1": ["pharmaceutical"], "10.2 2.2 7.6": ["households"], "0.8 15.6 26.9": ["hunting"], "-10.8 8.1 4.3": ["prevention"], "6.4 -7.1 1.3": ["highlighted"], "21.5 -1.2 2.4": ["announcing"], "1.5 9.8 4.4": ["insists"], "0.1 -0.5 0.2": ["reviews"], "2.6 9.2 5.8": ["daughters"], "8.6 22.3 0.0": ["capability"], "4.8 6.5 3.7": ["vice"], "12.0 17.6 7.7": ["weakness"], "3.6 -1.5 -1.1": ["flexible"], "1.2 2.3 -4.6": ["spokesperson"], "22.5 5.1 5.8": ["electronics"], "3.8 11.5 1.6": ["deny"], "8.8 10.0 7.8": ["structures"], "5.3 8.5 1.8": ["presidency"], "2.9 7.9 3.2": ["adequate"], "4.7 11.9 3.7": ["admit"], "-2.4 3.1 3.6": ["retire"], "13.4 22.0 8.7": ["forever"], "17.0 23.7 14.0": ["humans"], "0.8 -2.6 4.9": ["coordinator"], "22.4 5.7 1.8": ["telecommunications"], "-1.4 7.1 3.6": ["emphasis"], "6.3 7.9 -2.2": ["defended"], "-6.5 13.7 7.0": ["crossing"], "2.1 -2.4 -1.2": ["studied"], "-1.9 3.8 11.3": ["wages"], "3.4 4.8 -0.2": ["conversion"], "1.1 0.4 2.0": ["proceedings"], "11.4 10.9 17.0": ["sweet"], "2.3 9.9 6.3": ["rear"], "9.5 1.6 13.6": ["organic"], "-3.5 -2.2 4.3": ["hopeful"], "5.8 3.2 0.5": ["releases"], "5.3 16.5 8.3": ["aspect"], "12.3 12.9 15.1": ["gear"], "6.0 11.7 -1.0": ["superior"], "4.1 6.9 8.2": ["bands"], "2.1 -1.2 0.5": ["resolved"], "-6.8 0.3 6.9": ["salaries"], "-1.0 10.7 0.1": ["mental"], "1.2 4.7 7.3": ["homers"], "-6.2 7.8 2.8": ["liquidity"], "1.0 6.2 6.2": ["bedroom"], "-3.8 4.3 13.4": ["charter"], "13.4 9.0 4.9": ["entrance"], "3.1 9.5 26.7": ["lake"], "-1.6 -0.8 16.8": ["statewide"], "6.2 18.9 8.9": ["element"], "-1.3 9.7 1.5": ["camps"], "2.4 12.1 6.9": ["chase"], "7.3 9.0 -2.7": ["ambassador"], "4.8 10.9 3.2": ["difficulties"], "3.1 14.4 0.2": ["surveillance"], "5.7 0.4 6.7": ["totaled"], "6.6 34.6 -1.1": ["militant"], "-2.4 4.5 19.1": ["crop"], "0.8 16.3 2.4": ["fault"], "12.7 11.4 3.9": ["vowed"], "13.4 -0.1 5.8": ["thin"], "2.9 16.5 31.1": ["boats"], "23.9 6.6 0.8": ["dominant"], "11.9 5.4 -0.4": ["considerable"], "9.3 4.8 0.2": ["damages"], "7.2 7.2 30.3": ["fruit"], "10.1 12.2 4.8": ["stopping"], "16.0 6.1 -2.0": ["profitable"], "5.3 3.5 8.3": ["deciding"], "-7.1 0.5 6.8": ["nursing"], "13.7 7.3 21.7": ["tsunami"], "9.5 0.2 1.6": ["extending"], "3.0 12.0 3.3": ["semifinals"], "-5.0 5.2 2.6": ["input"], "-0.1 6.8 2.8": ["referendum"], "4.8 5.5 0.9": ["anniversary"], "-2.2 5.4 -3.9": ["respected"], "2.6 5.1 -3.0": ["violated"], "1.4 3.5 0.6": ["assess"], "1.4 15.4 15.0": ["puck"], "3.5 8.4 7.9": ["lenders"], "2.4 -8.2 2.5": ["arrangements"], "-4.4 4.1 5.8": ["criteria"], "10.4 3.0 -2.4": ["celebrating"], "-1.3 7.8 9.1": ["frustrated"], "12.3 7.6 0.6": ["marketplace"], "3.0 2.3 24.2": ["cooking"], "13.7 3.9 -0.4": ["install"], "-0.7 0.4 9.9": ["affecting"], "5.7 3.0 8.7": ["rugby"], "5.7 12.7 19.0": ["forest"], "13.1 8.3 10.2": ["cloud"], "17.4 10.3 7.5": ["contractor"], "5.9 16.0 9.7": ["chest"], "11.0 0.9 11.1": ["signature"], "-1.9 17.2 6.3": ["uniform"], "2.8 8.6 0.7": ["accidents"], "-1.7 9.6 1.9": ["intervention"], "2.9 8.9 4.1": ["tougher"], "14.2 6.1 3.6": ["teenager"], "5.3 6.9 19.0": ["gambling"], "0.9 2.0 12.1": ["mortgages"], "-1.1 2.4 -2.7": ["standings"], "-6.8 0.2 -2.1": ["evaluation"], "18.8 22.0 14.3": ["planet"], "4.8 3.7 9.8": ["dressed"], "6.6 16.0 4.3": ["underground"], "6.0 19.4 6.9": ["exact"], "-2.5 7.4 15.3": ["conservation"], "2.7 5.8 2.1": ["midfielder"], "-2.0 8.9 11.3": ["depend"], "9.9 3.9 0.6": ["replacing"], "9.8 3.6 5.5": ["headline"], "-8.8 6.3 -3.4": ["questioning"], "-2.2 9.1 6.0": ["athlete"], "6.7 3.4 -1.9": ["comparable"], "-9.2 9.0 3.3": ["accomplished"], "6.4 5.0 4.9": ["ordinance"], "5.9 14.6 6.9": ["feared"], "-0.6 1.4 1.9": ["discussing"], "-2.7 6.5 8.3": ["riders"], "4.9 -1.1 20.8": ["copper"], "10.3 12.8 8.1": ["unexpected"], "2.8 -2.4 2.0": ["administrators"], "3.4 3.2 1.1": ["favorable"], "13.2 10.5 16.4": ["painting"], "2.7 3.0 1.7": ["comply"], "12.6 -0.9 -1.9": ["headquartered"], "7.1 7.5 0.9": ["gross"], "3.7 5.1 6.2": ["picks"], "2.4 19.1 9.7": ["diplomatic"], "11.2 3.7 7.1": ["lighting"], "6.9 4.2 19.6": ["tobacco", "megayacht"], "-3.5 19.8 10.0": ["feelings"], "7.5 -3.8 4.7": ["pays"], "0.5 2.9 4.6": ["documentary"], "1.3 -3.8 -1.2": ["addresses"], "5.4 9.0 6.2": ["senators"], "-0.3 7.8 5.4": ["linebacker"], "5.6 1.6 9.4": ["cleaning"], "-1.0 11.6 1.9": ["withdrawal"], "10.5 8.1 6.7": ["brilliant"], "17.3 0.7 9.0": ["custom"], "-5.8 17.5 6.6": ["priorities"], "0.8 3.9 6.0": ["economist"], "4.8 5.8 3.3": ["waited"], "9.7 2.6 9.6": ["furniture"], "4.7 10.5 14.7": ["sub"], "6.4 8.8 9.9": ["turnover"], "11.3 10.5 1.1": ["costly"], "14.7 7.2 9.5": ["height"], "2.2 -3.0 -0.5": ["volumes"], "0.2 9.9 10.8": ["till"], "18.0 9.8 8.2": ["grab"], "5.2 5.2 0.7": ["completing"], "3.1 -1.6 11.5": ["sample"], "11.6 14.2 -5.2": ["equipped"], "2.3 -0.6 11.5": ["delegates"], "2.0 14.8 7.0": ["favorites"], "2.0 4.2 5.8": ["shortage"], "8.2 9.3 -0.7": ["publisher"], "3.7 2.0 4.0": ["estate"], "-2.9 18.5 3.3": ["hitter"], "14.4 6.3 3.8": ["globe"], "-1.3 1.5 -0.8": ["evaluate"], "13.1 1.2 2.0": ["sits"], "22.1 5.6 4.1": ["venture"], "9.4 7.7 10.2": ["shoppers"], "-0.9 9.6 1.9": ["designated"], "6.3 3.5 9.3": ["tying"], "7.2 13.6 1.9": ["signals"], "6.5 20.4 9.0": ["lesson"], "5.5 -2.8 -2.2": ["licensed"], "3.1 12.8 1.7": ["escaped"], "-3.2 -5.6 4.8": ["booked"], "2.5 13.3 9.4": ["survivors"], "-1.6 2.1 -0.7": ["integrity"], "2.9 3.2 6.9": ["unchanged"], "-0.4 5.7 2.9": ["trains"], "8.6 7.9 -1.0": ["mainstream"], "-1.3 6.6 1.7": ["ignored"], "3.9 9.7 -2.7": ["negotiate"], "-0.7 -0.5 1.7": ["receives"], "2.0 11.3 8.7": ["ethnic"], "3.0 -1.9 0.5": ["focuses"], "2.8 3.9 23.3": ["breakfast"], "0.1 1.8 0.6": ["laps"], "8.3 11.1 5.7": ["measured"], "10.6 -1.0 0.9": ["produces"], "1.1 19.6 12.7": ["skill"], "2.5 6.6 -1.5": ["indicates"], "10.9 9.3 10.3": ["branches"], "9.1 13.1 1.2": ["surrounded"], "-4.6 4.8 4.6": ["detention"], "2.0 10.4 0.5": ["tears"], "5.4 -2.5 -1.5": ["examine"], "14.5 13.4 -0.1": ["visible"], "11.2 13.0 6.0": ["steal"], "5.5 3.7 4.0": ["generations"], "2.9 4.0 3.9": ["deemed"], "7.0 13.0 0.8": ["fatal"], "13.0 10.6 8.3": ["mess"], "2.6 7.3 0.9": ["mandate"], "-1.3 -1.0 10.5": ["budgets"], "10.2 -4.7 -0.7": ["suite"], "5.0 13.2 10.7": ["deeper"], "2.8 20.4 4.8": ["pilots"], "11.2 4.2 1.6": ["publishing"], "8.4 11.2 23.2": ["grass"], "-1.6 0.3 16.4": ["meals"], "9.7 5.1 -5.0": ["enabled"], "5.5 8.3 5.9": ["footage"], "8.0 3.7 1.2": ["sections"], "1.8 9.6 1.4": ["transmission"], "7.0 14.0 3.3": ["everyday"], "20.1 20.6 8.3": ["literally"], "-2.7 4.6 9.5": ["tires"], "2.1 2.2 -1.2": ["acted"], "2.5 6.8 -3.3": ["photographs"], "11.9 6.5 -0.1": ["automotive"], "10.4 15.7 7.7": ["somehow"], "-1.7 -0.8 -6.0": ["investigated"], "5.7 -4.0 4.1": ["slated"], "15.8 5.1 10.5": ["dancing"], "9.5 9.4 0.4": ["electrical"], "12.2 3.0 10.0": ["bulk"], "13.4 2.0 1.7": ["designer"], "4.4 -0.6 8.6": ["highs"], "16.7 5.0 0.3": ["excluding"], "7.1 3.2 7.1": ["chamber"], "-1.7 4.7 -1.0": ["checking"], "6.5 5.7 28.7": ["corn"], "19.6 1.9 8.6": ["snapped"], "15.5 20.4 6.3": ["hidden"], "1.8 -6.1 6.5": ["scholarship"], "3.8 2.6 9.9": ["fundraising"], "16.8 -3.5 2.6": ["boosted"], "-4.0 20.1 2.2": ["moral"], "8.0 6.0 12.3": ["declining"], "2.0 8.6 4.1": ["trainer"], "8.8 4.8 0.1": ["proprietary"], "13.1 -0.9 6.8": ["bids"], "3.4 7.3 5.9": ["churches"], "0.8 12.6 5.0": ["audiences"], "16.4 3.0 -5.5": ["blew"], "6.8 5.9 9.6": ["crack"], "-0.6 9.3 -1.4": ["withdraw"], "2.2 4.8 1.0": ["gaining"], "13.5 4.0 5.3": ["tap"], "4.3 9.8 10.8": ["math"], "14.3 -9.5 7.2": ["wrapped"], "5.0 0.2 -0.2": ["thrilled"], "14.2 -2.3 -3.1": ["sued"], "7.8 3.4 2.0": ["charging"], "0.9 6.6 21.5": ["foods"], "3.8 2.2 5.3": ["arguing"], "12.7 4.3 5.4": ["placing"], "1.9 6.6 8.3": ["trades"], "-3.0 10.3 9.4": ["childhood"], "2.7 6.2 0.3": ["scope"], "15.4 8.4 0.8": ["lawsuits"], "4.2 5.3 1.1": ["disclosure"], "15.0 3.5 4.5": ["pump"], "1.5 4.1 6.0": ["inspection"], "7.7 15.0 6.8": ["villages"], "23.3 10.5 7.1": ["spin"], "12.9 16.2 6.0": ["knock"], "15.6 6.0 20.1": ["offshore"], "6.4 -8.6 12.8": ["capped"], "10.2 6.0 -2.0": ["formally"], "-9.0 8.7 4.0": ["physicians"], "12.1 13.4 -2.2": ["existence"], "-4.1 8.9 2.0": ["responsibilities"], "7.0 13.2 12.7": ["mood"], "0.5 2.8 4.9": ["witnessed"], "7.8 4.6 11.4": ["trophy"], "-3.0 0.6 3.3": ["grades", "osh"], "5.7 10.5 -2.3": ["oppose"], "5.6 8.4 4.9": ["airports"], "13.2 4.3 4.2": ["demonstration"], "0.9 11.8 -2.1": ["safely"], "7.5 8.5 1.8": ["litigation"], "1.0 6.6 4.6": ["incentive"], "19.2 5.8 7.7": ["fake"], "5.6 5.8 10.8": ["garage"], "-5.6 5.5 0.1": ["judicial"], "-1.5 9.2 2.0": ["arguments"], "1.9 12.6 16.6": ["catches"], "8.2 25.7 6.4": ["destruction"], "4.8 22.5 2.7": ["borders"], "7.5 5.1 10.4": ["disabled"], "2.6 -5.4 6.3": ["workshop"], "9.0 5.3 4.2": ["stream"], "16.3 10.5 6.4": ["strange"], "4.8 18.3 13.3": ["drill"], "12.8 4.9 1.3": ["divisions"], "4.3 -0.8 0.1": ["administrator"], "5.4 15.4 14.6": ["hunt"], "14.7 9.6 2.1": ["sophisticated"], "4.2 4.2 22.6": ["sugar"], "4.7 10.0 1.7": ["discrimination"], "-1.1 2.1 7.2": ["nationally"], "7.2 11.5 1.0": ["stance"], "0.6 4.5 -1.8": ["obligations"], "1.6 6.3 9.3": ["passage"], "8.0 4.2 5.8": ["workforce"], "15.6 -3.1 -1.3": ["announces"], "3.9 0.5 4.6": ["span"], "-3.7 6.5 7.3": ["restricted"], "0.5 -0.9 1.4": ["hearings"], "-8.1 12.5 6.1": ["punishment"], "5.3 9.9 15.1": ["immigrants"], "9.3 3.0 3.7": ["margins"], "9.9 2.1 3.4": ["excitement"], "3.0 19.6 6.9": ["diseases"], "6.9 10.0 1.5": ["lets"], "-5.4 10.4 8.9": ["discipline"], "14.3 5.2 7.3": ["toys"], "2.5 9.4 8.4": ["wage"], "4.7 -1.0 2.4": ["accepting"], "-1.8 5.4 8.3": ["balanced"], "0.8 3.0 -6.5": ["accessible"], "2.5 11.6 -0.9": ["actively"], "9.8 9.6 3.4": ["jet"], "8.3 1.8 5.6": ["architecture"], "16.9 8.2 4.5": ["illegally"], "1.5 13.6 4.7": ["personality"], "6.2 13.0 10.6": ["debris"], "-0.4 7.1 -0.5": ["responding"], "10.5 0.7 8.5": ["fines"], "-6.2 17.5 5.5": ["replied"], "12.1 5.2 15.3": ["aging"], "7.3 3.8 10.2": ["fed"], "10.2 1.7 7.0": ["filling"], "8.4 9.2 3.8": ["activist"], "10.7 11.1 8.5": ["march"], "-5.0 0.9 0.3": ["tenure"], "4.7 11.1 -0.1": ["hometown"], "8.2 7.4 5.4": ["pocket"], "12.3 14.4 1.7": ["conventional"], "11.4 2.9 5.0": ["segments"], "6.3 12.6 0.8": ["burn"], "9.4 2.9 11.0": ["yuan"], "6.7 14.7 -1.6": ["battling"], "7.5 7.0 12.7": ["quake"], "-0.1 15.6 7.5": ["currencies"], "0.7 3.4 0.6": ["exceptional"], "12.0 7.7 -0.2": ["strongest"], "3.1 19.8 3.9": ["encounter"], "8.6 7.3 11.8": ["perfectly"], "6.5 5.8 11.2": ["bottle"], "13.5 10.0 4.0": ["lady"], "9.7 8.1 12.9": ["slip"], "1.0 15.6 9.7": ["laugh"], "2.1 1.4 35.9": ["beef"], "19.9 3.0 -0.2": ["overhaul"], "12.5 11.9 3.8": ["buyer"], "-4.4 18.4 -1.1": ["rank"], "4.6 2.9 9.0": ["locally"], "7.8 18.2 3.8": ["principle"], "5.7 3.4 4.7": ["framework"], "8.2 33.3 1.1": ["rebel"], "10.1 10.0 3.2": ["blaze"], "13.2 6.4 1.2": ["patent"], "8.1 4.3 6.4": ["collecting"], "8.2 15.3 7.0": ["rid"], "9.6 20.3 5.9": ["devastating"], "2.7 5.0 4.4": ["donors"], "1.5 5.0 7.2": ["identification", "cuffs"], "-3.1 7.1 0.9": ["editorial"], "11.0 11.2 3.1": ["compound"], "1.4 -2.3 8.0": ["networking"], "-1.3 8.6 -1.0": ["prevented"], "1.9 5.9 7.9": ["uncertain"], "6.9 2.1 9.7": ["babies"], "8.9 2.9 7.0": ["slight"], "6.9 2.4 7.0": ["removal"], "10.1 13.5 12.4": ["storms"], "4.5 9.2 2.8": ["greatly"], "0.7 19.6 -2.3": ["torture"], "8.2 15.5 7.8": ["trapped"], "11.3 6.3 7.9": ["roots"], "3.8 18.2 6.2": ["difficulty"], "8.4 3.5 12.0": ["slowed"], "-0.6 13.1 2.9": ["physically"], "14.8 5.3 10.4": ["specialty"], "13.5 9.4 7.6": ["weaker"], "-1.9 5.3 0.8": ["insight"], "12.6 0.9 8.4": ["fined"], "1.7 5.5 13.7": ["diet"], "2.5 4.6 11.3": ["commodities"], "5.1 10.6 15.4": ["pollution"], "1.3 7.6 1.0": ["gym"], "12.3 -1.7 6.1": ["triggered"], "-3.3 2.8 14.6": ["tournaments"], "4.3 4.6 -0.5": ["km"], "15.1 4.2 -4.9": ["newest"], "3.6 -6.1 -0.5": ["accommodate"], "6.4 12.9 2.5": ["unfair"], "-2.3 14.3 5.9": ["humanitarian"], "1.2 7.1 -0.3": ["achievements"], "-3.5 8.1 0.8": ["offenses"], "5.2 9.9 0.6": ["intersection"], "-2.1 0.3 4.4": ["repairs"], "1.5 7.1 2.6": ["executed"], "6.1 8.2 16.4": ["flowers"], "-1.0 10.5 4.7": ["parliamentary"], "-1.5 12.6 14.0": ["assumptions"], "-3.3 12.5 6.9": ["batting"], "5.3 6.1 -1.7": ["breach"], "-5.6 3.7 3.3": ["reductions"], "21.6 6.0 4.3": ["stunning"], "2.2 9.3 0.8": ["suspicious"], "2.8 -0.9 0.2": ["appealed"], "14.1 6.3 5.7": ["pointing"], "4.4 3.9 9.5": ["finale"], "9.8 6.6 2.1": ["profitability"], "5.9 0.9 0.5": ["suitable"], "3.0 9.8 2.0": ["establishing"], "10.2 4.2 28.3": ["chips"], "-2.2 7.9 2.4": ["responses"], "5.8 19.9 10.8": ["dying"], "8.6 3.0 6.7": ["tune"], "17.2 20.0 14.7": ["sky"], "-0.9 12.1 -0.7": ["remembered"], "8.6 3.0 7.9": ["prizes"], "8.4 11.1 4.3": ["discover"], "6.1 5.7 0.1": ["generating"], "12.2 2.9 8.6": ["slowdown"], "2.6 10.6 10.0": ["frustration"], "14.2 20.9 10.1": ["surely"], "16.2 12.8 9.4": ["circle"], "-4.5 9.2 15.5": ["drought"], "22.6 10.4 9.0": ["spectacular"], "-2.8 -1.8 4.5": ["musicians"], "8.9 23.6 3.5": ["hell"], "7.4 5.2 9.8": ["lock"], "8.2 11.4 7.9": ["dreams"], "3.0 8.7 11.6": ["impose"], "18.7 3.0 1.2": ["displays"], "13.5 3.9 10.3": ["temporarily"], "4.8 17.9 3.6": ["button"], "-1.2 17.1 -2.9": ["communicate"], "-1.1 6.4 3.1": ["arriving"], "13.1 5.4 10.4": ["trailer"], "12.5 -7.9 0.7": ["licensing"], "8.4 13.4 5.6": ["wheel"], "0.7 0.8 6.1": ["lasted"], "14.3 15.7 35.7": ["ocean"], "6.4 6.1 -1.2": ["tribute"], "5.1 4.9 5.1": ["urge"], "0.6 4.6 4.2": ["meaningful"], "-2.2 8.3 6.0": ["anticipate"], "-2.5 3.8 3.6": ["attributed"], "8.3 9.6 4.5": ["automatic"], "11.8 -6.1 -1.3": ["prestigious"], "-2.8 6.4 7.4": ["treatments"], "0.6 -0.1 2.9": ["finances"], "1.6 5.7 1.4": ["suggestions"], "2.8 10.8 4.8": ["parked"], "0.5 8.0 2.5": ["frequent"], "5.5 -1.7 7.2": ["declines"], "16.9 6.2 10.1": ["pole"], "-0.4 0.5 2.3": ["restored"], "11.8 12.9 24.6": ["shore", "cuds"], "5.5 1.7 13.9": ["n"], "12.0 5.0 8.1": ["enterprises"], "4.9 0.6 -4.3": ["joins"], "-2.0 6.9 8.2": ["transit"], "6.4 11.2 4.7": ["formation"], "8.9 6.9 5.1": ["viewing"], "2.7 8.0 -4.0": ["negotiating"], "17.4 3.5 7.5": ["rises"], "-4.7 12.2 2.7": ["productive"], "2.9 14.5 5.0": ["unity"], "8.0 9.7 11.0": ["finger"], "6.8 13.1 5.7": ["infected"], "-3.6 10.9 1.8": ["achieving"], "10.0 4.9 9.5": ["sporting"], "-3.9 8.0 8.9": ["divorce"], "12.3 24.8 5.2": ["hide"], "8.5 5.5 4.2": ["disappeared"], "5.2 12.6 6.6": ["crowds"], "13.7 8.8 6.4": ["duo"], "-2.1 9.2 5.0": ["acceptable"], "7.3 -1.8 0.9": ["donate"], "-0.3 11.2 -1.6": ["pursuing"], "5.9 7.9 2.9": ["rotation"], "5.3 5.9 4.8": ["wound"], "4.9 -4.0 0.5": ["speakers"], "3.6 5.5 4.8": ["considers"], "8.0 -0.4 5.1": ["accounted"], "3.2 5.6 2.0": ["describes"], "-8.5 9.1 6.0": ["physician"], "2.1 2.5 2.4": ["contemporary"], "6.9 2.5 14.0": ["matching"], "13.9 9.6 8.9": ["chemicals"], "3.1 0.4 1.2": ["jailed"], "-1.0 -1.4 -1.4": ["commitments"], "0.9 1.4 -0.8": ["notified"], "-2.8 3.6 -2.2": ["maintains"], "8.6 2.8 2.6": ["pleaded"], "6.3 2.7 7.5": ["diversity"], "8.8 2.5 6.4": ["teenagers"], "3.5 15.7 2.5": ["painful"], "-8.5 3.3 -3.8": ["drafted"], "-1.9 8.8 7.4": ["explanation"], "2.2 1.2 -0.7": ["assisted"], "2.8 9.4 -4.9": ["safer"], "7.1 9.0 7.8": ["boyfriend", "photoset"], "5.9 4.3 1.3": ["convince"], "12.0 38.3 4.0": ["destroy"], "2.2 8.7 11.7": ["formula"], "20.7 5.7 0.5": ["blown"], "16.5 5.3 10.5": ["odd"], "-4.4 5.8 2.6": ["baseman"], "13.5 2.1 1.9": ["holders"], "13.2 27.8 3.8": ["wars"], "2.6 10.5 37.3": ["coastal"], "4.8 8.9 6.8": ["grandchildren"], "-0.6 13.6 0.3": ["impression"], "10.9 -3.3 -0.9": ["showcase"], "5.4 -3.6 4.1": ["manages"], "22.8 -0.2 0.2": ["surged"], "13.4 4.6 7.1": ["trio"], "-0.6 2.9 7.9": ["contributing"], "2.6 3.7 2.7": ["caution"], "-0.5 5.7 14.6": ["provinces"], "1.7 4.9 10.1": ["description"], "-0.8 4.8 -0.7": ["grateful"], "7.2 28.9 -0.1": ["bombs"], "0.1 3.8 15.6": ["cocaine"], "-3.8 10.3 4.0": ["unbeaten"], "0.6 9.9 26.8": ["wildlife"], "13.2 1.9 4.1": ["edged", "taspo"], "0.6 7.1 2.9": ["understands"], "6.0 1.3 0.3": ["usage"], "-7.2 6.1 -0.9": ["coached"], "6.2 7.2 2.3": ["jurors"], "2.2 4.6 5.7": ["accordance"], "3.8 -2.9 -1.4": ["reviewing"], "5.5 2.0 3.9": ["subscription"], "-1.0 11.6 3.2": ["suspicion"], "3.8 4.7 -0.8": ["rankings"], "0.9 13.5 4.4": ["philosophy"], "-4.7 9.1 4.0": ["occasions"], "1.4 6.8 12.2": ["shirt"], "4.6 23.2 8.3": ["whenever"], "5.7 -3.1 10.5": ["underway"], "-0.5 7.6 2.8": ["implementing"], "-2.3 8.4 1.7": ["killings"], "13.5 3.4 7.1": ["demonstrations"], "3.1 8.5 6.2": ["approaches"], "0.2 14.5 2.7": ["indictment"], "-4.0 6.7 1.0": ["fortunate"], "17.4 7.4 -5.8": ["subsidiaries"], "24.4 -0.7 8.9": ["mini"], "9.2 3.8 1.5": ["dual"], "2.4 4.3 16.9": ["swimming"], "16.0 -3.5 -1.2": ["fueled"], "5.5 0.5 4.9": ["proceed"], "7.5 9.4 2.5": ["emerge"], "8.1 8.0 17.9": ["wet"], "3.5 14.2 7.9": ["fights"], "10.0 25.3 14.9": ["rocket"], "-0.1 -4.8 -1.2": ["examined"], "4.6 3.8 0.7": ["respondents"], "14.0 13.0 4.1": ["blocking"], "0.1 13.9 1.1": ["preventing"], "13.8 3.1 4.6": ["majors"], "5.6 -0.9 -0.5": ["guarantees"], "2.5 8.5 7.9": ["disappointment"], "9.6 10.2 10.7": ["counting"], "1.6 12.5 7.9": ["wise"], "1.7 8.8 1.5": ["treating"], "1.8 2.9 1.0": ["cautious"], "5.7 29.2 8.9": ["tactics"], "5.2 7.4 4.0": ["examples"], "12.1 2.5 9.5": ["kicks"], "19.0 10.5 9.3": ["shake"], "7.8 2.8 0.2": ["headlines"], "5.4 8.1 9.2": ["carbon"], "3.2 10.0 8.0": ["sisters", "conditon"], "2.2 7.8 5.9": ["ethics"], "1.7 8.2 3.7": ["choosing"], "3.8 0.8 0.1": ["oversight"], "-2.7 5.9 1.9": ["doubts"], "7.4 15.3 3.0": ["reader"], "-0.6 3.4 0.9": ["youngest", "expences"], "19.1 26.6 7.6": ["killer"], "2.4 10.9 15.5": ["bats"], "1.5 6.2 17.8": ["ounce"], "9.4 1.4 1.6": ["appearing"], "10.7 7.9 2.6": ["neutral"], "5.3 4.4 10.9": ["projections"], "12.1 0.3 5.0": ["suburban"], "-2.8 5.4 5.1": ["nurses", "coachs"], "-2.1 10.2 -6.2": ["advocate"], "8.1 13.8 4.0": ["joy"], "7.8 5.3 -1.2": ["pledge"], "3.2 5.5 -3.6": ["disclose"], "15.2 9.9 26.6": ["cat"], "0.9 6.4 -1.9": ["praise"], "6.5 12.3 14.2": ["cargo"], "13.9 4.5 11.6": ["slowing"], "-0.1 12.5 4.3": ["wishes"], "14.0 6.8 12.9": ["wholesale"], "-5.3 7.6 -4.2": ["conversations"], "5.9 12.6 7.1": ["struggles"], "6.3 -1.7 1.6": ["consists"], "0.7 11.5 4.6": ["depression"], "-5.9 11.6 1.7": ["elect"], "18.4 15.3 14.6": ["waves"], "10.0 8.9 12.8": ["import"], "6.6 2.8 3.0": ["instruments"], "-4.9 -3.5 4.3": ["foster"], "13.6 8.2 6.4": ["utilities"], "-0.7 7.5 4.3": ["surplus"], "-6.0 16.6 3.0": ["ambulance"], "2.6 17.7 0.2": ["occupied"], "-1.0 1.8 -0.2": ["careers"], "-1.9 6.7 9.8": ["offseason"], "2.1 9.0 1.3": ["exists"], "7.0 7.8 11.7": ["servers"], "2.8 12.9 2.3": ["gate"], "5.5 -0.2 1.9": ["titled"], "2.6 1.8 2.8": ["trailed"], "3.3 7.9 -1.2": ["inappropriate"], "7.5 20.5 6.7": ["hearts"], "16.5 7.1 18.3": ["spill"], "-4.9 3.9 -4.1": ["amended"], "12.8 3.0 -0.7": ["warnings"], "8.4 9.6 3.7": ["engines"], "4.6 6.9 3.1": ["desk"], "3.8 17.1 12.0": ["nose"], "1.6 4.3 2.5": ["compare"], "-6.3 12.1 10.6": ["deputies"], "10.6 2.8 20.3": ["freeze"], "-1.1 12.5 3.6": ["unfortunate"], "-0.1 9.7 3.6": ["sing"], "1.2 11.7 7.8": ["batters"], "-0.2 8.7 -1.1": ["deserves"], "-1.7 2.7 8.1": ["slot"], "4.7 4.5 40.4": ["rice"], "-2.2 15.3 7.3": ["infection"], "-1.4 14.7 7.8": ["interception"], "7.8 17.0 3.1": ["closest"], "5.1 7.3 9.3": ["peers"], "5.2 -1.8 -1.7": ["compelling"], "15.7 3.9 6.5": ["ambitious"], "4.4 6.0 6.6": ["bullpen"], "8.2 23.0 13.3": ["soul"], "-1.6 6.9 6.6": ["affects"], "22.3 13.6 25.6": ["moon"], "-2.0 0.4 2.5": ["appeals"], "10.7 4.4 5.6": ["combine"], "4.6 1.3 1.0": ["sealed"], "7.8 8.8 6.5": ["lone"], "-0.1 9.5 9.0": ["humor"], "15.5 14.9 3.0": ["symbol"], "2.4 9.7 2.9": ["assumed"], "5.8 16.5 4.9": ["scared"], "11.9 -3.7 -0.9": ["employs"], "14.4 49.3 5.0": ["evil"], "9.3 15.4 3.3": ["spreading"], "-7.3 7.0 12.0": ["motorcycle"], "9.5 7.3 2.8": ["excessive"], "1.4 8.2 2.8": ["cautioned"], "7.1 -3.1 7.6": ["recycling"], "5.3 4.8 5.4": ["mothers"], "2.1 9.8 13.2": ["counted"], "11.6 5.8 -7.0": ["exclusively"], "1.0 2.0 1.5": ["graduates"], "6.1 1.0 8.5": ["curb"], "-4.6 5.5 5.7": ["superintendent"], "9.0 8.9 -5.2": ["convert"], "17.1 7.9 5.3": ["stealing"], "4.1 7.2 -0.8": ["evacuated"], "2.6 3.1 4.8": ["exceed"], "-0.6 4.4 7.1": ["tours"], "26.9 9.4 11.0": ["tall"], "8.4 15.6 7.2": ["threaten"], "5.7 16.4 31.2": ["vessel"], "5.7 4.4 6.2": ["shy"], "-7.9 19.8 4.1": ["incumbent"], "10.0 6.9 12.4": ["patterns"], "-3.8 -2.3 3.9": ["valid"], "-4.8 8.0 -0.5": ["reminded"], "6.3 33.8 7.1": ["criminals"], "12.4 5.0 9.3": ["heritage"], "11.5 -1.6 10.0": ["smooth"], "5.0 9.1 5.7": ["interior"], "14.1 3.7 1.8": ["burst"], "5.8 15.6 5.6": ["ignore"], "16.6 1.8 12.0": ["lowered"], "11.2 16.6 3.4": ["flames"], "7.9 9.4 8.6": ["broker"], "22.7 8.0 -0.2": ["lobby"], "2.9 3.4 1.9": ["substantially"], "2.5 10.4 6.4": ["approaching"], "18.0 -1.7 7.5": ["poised"], "7.9 10.2 -1.9": ["loud"], "-4.6 1.4 10.0": ["enrollment"], "11.5 16.5 -6.5": ["radical"], "8.9 3.6 10.0": ["drinks"], "13.7 20.4 6.6": ["awesome"], "8.7 11.7 13.0": ["technique"], "6.3 11.9 7.6": ["dealer"], "9.9 6.6 48.2": ["chicken"], "1.0 1.0 2.9": ["acceptance"], "-4.1 6.4 5.7": ["appreciation"], "9.9 3.3 11.5": ["figured"], "10.8 5.3 -3.3": ["globally"], "11.0 -2.0 3.3": ["arrangement"], "13.9 10.4 7.4": ["drops"], "4.4 0.1 4.8": ["mandatory"], "16.9 5.2 14.0": ["tables"], "8.7 10.0 1.7": ["dies"], "4.1 7.8 5.2": ["collision"], "2.8 9.0 19.8": ["ingredients"], "6.3 1.4 -7.4": ["partnerships"], "-5.8 7.2 -2.0": ["resign"], "-1.5 12.5 -1.1": ["helpful"], "13.2 6.9 8.5": ["stakes"], "-6.4 13.1 4.2": ["interceptions"], "11.8 14.0 22.8": ["stone"], "0.1 17.6 0.5": ["prayer"], "13.8 14.7 27.9": ["sand"], "2.7 5.0 3.8": ["draws"], "6.1 6.7 7.6": ["motor"], "1.4 11.2 -0.3": ["aviation"], "9.9 13.8 4.6": ["solely"], "-4.0 5.8 8.7": ["guitar"], "5.0 17.6 5.0": ["overwhelming"], "2.3 7.0 12.8": ["elementary"], "-2.1 -2.4 -0.8": ["rehabilitation"], "25.8 12.3 19.7": ["king"], "9.6 2.7 -0.4": ["devoted"], "6.5 16.7 9.2": ["lands"], "11.0 5.0 -3.0": ["northwest"], "6.3 10.7 3.2": ["volatile"], "-2.2 15.3 6.8": ["tribal"], "2.2 14.3 -1.2": ["accusations"], "-2.8 13.5 20.4": ["crops"], "-7.6 9.0 5.8": ["script"], "8.8 10.6 13.7": ["catching"], "8.4 4.2 5.3": ["wealthy"], "-2.1 14.0 2.6": ["effectiveness"], "15.3 6.0 10.6": ["bidding"], "2.2 4.1 13.2": ["wrestling"], "20.3 5.3 11.7": ["vendor"], "7.4 2.2 -0.1": ["implications"], "19.7 11.6 2.7": ["tower"], "5.3 4.5 3.4": ["recalls"], "16.2 4.2 2.9": ["hybrid"], "6.8 6.0 2.5": ["genuine"], "4.1 9.5 6.1": ["fails"], "4.4 4.4 -2.9": ["scrutiny"], "5.5 1.5 5.2": ["venues"], "4.1 16.7 8.8": ["rebuild"], "7.9 28.3 -1.8": ["hiding"], "8.1 4.2 -2.9": ["milestone"], "3.9 1.8 8.1": ["strict"], "6.1 1.9 6.1": ["wondering"], "3.4 6.4 10.8": ["referee"], "8.2 11.0 9.9": ["replay"], "2.0 10.7 17.1": ["knife"], "3.4 13.4 -2.3": ["silence"], "-2.1 10.8 4.1": ["credibility"], "10.4 0.7 3.2": ["oriented"], "7.7 2.3 3.9": ["hung"], "10.9 11.7 5.7": ["removing"], "11.4 7.4 10.4": ["traditionally"], "0.6 15.4 3.2": ["intensity"], "25.6 12.2 0.6": ["corporation"], "14.8 -1.4 5.0": ["bounced"], "-1.4 -2.2 0.4": ["dated"], "-5.4 15.7 1.1": ["nominee"], "6.9 25.1 3.7": ["opposing"], "8.6 2.3 5.0": ["enthusiasm"], "0.1 -1.7 0.8": ["certification"], "5.9 5.6 19.1": ["trash"], "8.5 26.3 4.1": ["battles"], "1.8 1.3 1.1": ["retiring"], "3.0 12.6 9.5": ["realistic"], "9.7 1.7 4.2": ["observers"], "8.4 1.5 6.9": ["lengthy"], "7.8 0.4 1.4": ["premiere"], "3.7 16.2 3.0": ["isolated"], "6.9 -0.3 -0.1": ["spotlight"], "2.0 15.6 -1.0": ["inspiration"], "4.8 12.9 11.1": ["trigger"], "6.6 -3.1 3.4": ["staged"], "17.2 4.5 29.5": ["frozen"], "3.4 -0.6 2.4": ["initiated"], "5.0 4.9 4.2": ["alternatives"], "5.1 33.6 11.4": ["missile"], "-5.7 11.1 8.2": ["pitchers"], "3.8 13.8 3.7": ["avoided"], "5.2 10.0 7.4": ["dependent"], "9.5 9.4 0.2": ["pose"], "7.8 1.8 14.8": ["contests"], "0.9 5.3 -0.3": ["searched"], "1.7 5.1 14.6": ["gallons"], "-6.4 6.4 -1.4": ["appreciated"], "5.8 0.1 5.6": ["awaiting"], "-0.7 1.3 -0.6": ["facilitate"], "-7.3 5.9 9.0": ["sentencing"], "13.8 5.7 11.3": ["slump"], "2.2 4.7 2.8": ["invitation"], "10.9 5.0 8.7": ["shipments"], "1.3 30.9 11.0": ["occupation"], "3.4 16.2 7.7": ["expression"], "3.7 7.6 6.5": ["cope"], "-0.2 -2.1 11.9": ["remainder"], "9.1 0.8 5.6": ["reflecting"], "10.7 2.4 -1.5": ["distribute"], "-8.1 6.1 5.0": ["strikeouts"], "7.8 17.5 5.9": ["movements"], "9.6 1.4 11.6": ["bonuses"], "5.0 9.5 -0.5": ["confirmation"], "9.1 17.4 8.1": ["notion"], "-2.7 14.6 6.9": ["aide"], "2.1 1.7 15.3": ["fare"], "-7.0 4.6 8.1": ["medication"], "12.8 0.1 5.1": ["laboratory"], "7.7 9.3 3.3": ["rescued"], "3.0 8.2 10.6": ["exchanges"], "4.3 15.8 10.5": ["joke"], "23.0 10.9 5.1": ["screens"], "-2.0 -1.4 11.7": ["jewelry"], "2.9 3.5 -5.8": ["dedication"], "8.6 11.6 6.1": ["pressing"], "13.6 0.7 10.9": ["cent"], "5.6 7.6 7.5": ["nowhere"], "-4.9 13.1 0.6": ["engagement"], "11.8 -0.5 9.4": ["crown"], "-4.0 5.4 -1.2": ["recruit"], "18.6 10.3 7.2": ["legendary"], "16.6 3.0 1.8": ["businessman"], "17.1 13.9 15.1": ["ancient"], "6.2 6.6 6.4": ["alike"], "3.7 -8.0 1.6": ["postponed"], "7.3 4.9 3.1": ["constitute"], "5.6 5.8 2.9": ["courtroom"], "-1.0 -3.8 -7.8": ["endorsed"], "10.0 4.7 -0.3": ["supplied"], "-0.8 5.2 0.1": ["testify"], "5.5 1.3 6.6": ["youngsters"], "6.8 8.3 -0.1": ["releasing"], "10.4 8.2 8.5": ["mystery"], "1.9 2.5 7.0": ["applying"], "2.2 9.4 6.2": ["sustain"], "3.2 3.2 6.7": ["commentary"], "-5.8 6.6 1.0": ["timely"], "3.0 9.9 1.4": ["default"], "6.4 7.3 6.2": ["wire"], "-5.2 20.9 -3.7": ["loyal"], "-0.2 13.5 1.8": ["engaging"], "2.3 -0.3 4.3": ["agrees"], "9.5 9.4 41.4": ["eggs"], "3.2 14.2 -0.5": ["kidnapping"], "11.6 -3.2 3.5": ["totaling"], "-1.3 3.9 4.4": ["warrants"], "5.6 9.1 -3.0": ["condemned"], "-4.7 -3.3 0.6": ["counseling"], "19.0 8.6 9.8": ["jumping"], "5.6 4.5 1.7": ["reveals"], "0.3 12.1 0.5": ["classified"], "8.6 38.8 7.9": ["ally"], "7.6 5.4 1.0": ["consolidation"], "-5.7 9.9 7.7": ["wickets"], "10.4 -11.3 -6.2": ["conjunction"], "4.5 5.7 1.2": ["indicating"], "7.8 10.0 2.1": ["crowded"], "8.4 11.0 5.4": ["gradually"], "17.9 6.8 6.5": ["mere"], "9.4 23.2 8.3": ["object"], "-3.9 5.9 35.9": ["vegetables"], "4.0 1.8 0.6": ["organize"], "6.9 25.5 7.8": ["helicopters"], "11.5 3.7 9.3": ["strip"], "8.2 6.4 1.5": ["instructions"], "2.0 17.3 4.7": ["politician"], "-3.8 13.1 0.7": ["spiritual"], "4.7 10.0 -0.2": ["urgent"], "1.7 4.8 4.8": ["concentrate"], "0.7 1.9 3.4": ["th"], "8.5 12.1 5.7": ["chaos"], "21.1 13.4 -1.3": ["revolution"], "-1.9 5.6 7.1": ["substitute"], "8.3 5.1 -2.3": ["advances"], "1.9 -5.0 4.9": ["finishes"], "-5.7 7.5 6.3": ["wells"], "23.4 1.8 0.2": ["sweeping"], "5.9 10.2 6.5": ["pressed"], "-4.1 8.0 5.6": ["adjustments"], "-5.9 9.6 2.1": ["contacts"], "5.0 8.2 11.7": ["mound"], "14.9 6.4 12.2": ["terminal"], "17.7 8.4 10.9": ["bounce"], "6.7 4.8 4.8": ["turmoil"], "5.5 7.5 9.8": ["spell"], "0.2 4.8 5.9": ["payroll"], "1.3 4.3 6.0": ["belt"], "0.9 7.4 4.5": ["nurse"], "3.5 13.8 5.1": ["semifinal"], "-3.4 0.2 0.3": ["hospitalized"], "-4.3 1.2 9.9": ["jazz"], "1.4 6.5 2.9": ["credited"], "10.4 6.4 8.2": ["downturn"], "8.0 0.4 12.1": ["log"], "5.0 14.5 11.6": ["outbreak"], "-2.3 14.4 3.9": ["frustrating"], "1.9 0.2 -1.1": ["voluntary"], "5.0 8.9 9.1": ["motorists"], "18.1 6.8 15.1": ["thick"], "10.3 3.0 10.4": ["desktop"], "13.9 10.9 5.8": ["dust"], "11.2 1.4 -0.9": ["specialized"], "0.3 21.3 4.8": ["pursuit"], "-0.7 4.1 6.4": ["experiencing"], "-7.0 3.8 1.9": ["stays"], "2.8 16.1 0.6": ["forgotten"], "5.3 -4.3 3.0": ["appealing"], "3.6 6.7 5.2": ["favored"], "-0.6 6.0 6.4": ["briefing"], "9.6 19.0 13.2": ["pit"], "4.9 11.8 13.0": ["commodity"], "10.4 8.1 8.5": ["iron"], "2.5 0.9 -1.9": ["functionality"], "1.5 12.7 0.8": ["identifying"], "0.0 4.6 5.4": ["overs"], "5.6 6.9 23.8": ["farms"], "11.8 6.1 3.3": ["stepping"], "-2.5 2.5 1.4": ["deserved"], "14.0 5.0 4.3": ["bearing"], "3.8 11.6 -0.3": ["acknowledge"], "4.5 16.9 9.5": ["hardest"], "4.6 11.8 6.0": ["environments"], "-3.5 5.9 2.8": ["compiled"], "13.3 10.3 5.7": ["visual"], "2.3 6.8 -0.2": ["strengthening"], "4.8 16.5 4.8": ["explosives"], "-0.3 7.8 6.4": ["reluctant"], "5.5 13.0 20.9": ["craft"], "18.4 16.4 11.0": ["magic"], "5.5 8.2 7.3": ["gallery"], "3.6 16.1 0.2": ["tasks"], "4.4 -2.6 4.1": ["inaugural"], "10.2 -1.2 8.9": ["generous"], "4.5 5.3 6.0": ["layoffs"], "28.2 -3.6 1.3": ["landmark"], "8.5 20.9 11.4": ["zones"], "2.4 11.4 -1.8": ["successor"], "6.1 5.4 -3.2": ["influential"], "8.2 6.7 9.5": ["dividends"], "26.7 3.5 1.2": ["hub"], "6.4 8.8 -1.6": ["violate"], "-2.0 11.2 0.3": ["voices"], "2.2 8.5 7.2": ["chat"], "-0.9 3.9 0.8": ["vacant"], "1.6 6.2 15.2": ["legislature"], "16.9 -6.1 5.9": ["packaging"], "4.1 3.4 6.5": ["sometime"], "2.7 9.7 7.4": ["strain"], "2.6 8.9 5.1": ["governance"], "17.2 8.8 4.9": ["pure"], "15.4 11.3 9.3": ["seemingly"], "0.5 2.2 -1.7": ["transparency"], "6.6 5.5 2.3": ["legally"], "6.6 2.0 7.0": ["optimism"], "25.2 1.3 0.1": ["logo"], "8.9 0.2 -2.7": ["excellence"], "8.0 7.4 6.4": ["advisers"], "8.5 9.6 5.9": ["refuse"], "4.8 2.0 7.6": ["performers"], "5.9 4.7 4.6": ["speeds"], "-0.2 6.2 3.5": ["permitted"], "0.6 -0.9 7.9": ["entries"], "2.9 3.7 1.1": ["lasting"], "-6.5 7.4 16.8": ["foreclosure"], "12.7 17.0 38.9": ["bird"], "10.6 14.8 5.6": ["chart"], "-1.6 11.6 9.3": ["aides"], "1.7 15.7 5.3": ["incredibly"], "12.5 2.4 18.6": ["seal"], "4.3 5.2 2.1": ["economics"], "-0.2 18.7 12.1": ["beliefs"], "-4.5 -2.1 -1.0": ["consultation"], "-0.0 11.6 1.4": ["tragic"], "9.2 20.8 8.4": ["adventure"], "7.9 1.3 4.6": ["reaches"], "14.2 12.9 3.4": ["collective"], "10.1 17.2 1.6": ["controlling"], "7.6 0.8 -2.1": ["reject"], "2.5 5.1 1.5": ["governing"], "1.7 7.4 1.6": ["evident"], "14.0 12.4 18.8": ["hungry"], "10.9 8.1 17.9": ["gray"], "6.5 6.5 3.3": ["stored"], "-1.1 3.0 7.2": ["softball"], "6.4 5.6 7.0": ["clerk"], "2.4 7.1 0.5": ["advisor"], "7.5 3.6 -2.3": ["fame"], "15.0 6.6 6.2": ["array"], "7.7 9.6 2.8": ["barrier"], "6.5 9.3 30.6": ["salt"], "-4.4 3.1 -1.4": ["emphasized"], "1.0 7.5 5.3": ["steals"], "5.2 7.5 0.9": ["violating"], "5.7 6.8 10.9": ["grandmother"], "-1.0 21.0 7.0": ["detainees"], "6.1 6.0 -0.8": ["advocacy"], "1.7 2.0 9.8": ["spectrum"], "4.9 2.8 -3.5": ["reiterated"], "0.3 6.0 5.5": ["explaining"], "3.0 16.4 14.7": ["conservatives"], "10.0 4.3 2.1": ["northeast"], "1.2 34.2 5.1": ["casualties"], "16.1 7.3 8.5": ["sorts"], "5.2 10.3 0.4": ["sends"], "13.4 3.5 8.2": ["mall"], "21.1 1.2 9.7": ["plunged"], "-0.6 16.5 6.7": ["matchup"], "2.1 0.1 0.7": ["indicted"], "2.0 6.8 11.3": ["tire"], "17.2 15.8 7.4": ["automaker"], "1.6 3.4 2.9": ["commenting"], "7.0 22.3 4.7": ["perception"], "0.0 9.5 4.9": ["differently"], "5.5 13.2 11.2": ["dirt"], "13.0 11.1 -0.4": ["leak"], "9.5 17.1 9.6": ["loving"], "11.4 13.7 3.9": ["embassy"], "-4.5 5.5 22.2": ["cattle"], "8.7 -0.3 2.8": ["crackdown"], "8.9 5.8 4.5": ["shipped"], "0.9 6.7 3.8": ["confusion"], "12.5 9.3 8.4": ["insurers"], "3.1 4.6 8.2": ["committees"], "14.3 8.4 9.6": ["scientist"], "18.3 3.4 -8.8": ["branded"], "0.9 15.8 9.4": ["adjust"], "9.1 7.6 8.7": ["grid"], "4.1 4.9 3.2": ["accelerate"], "4.9 8.0 8.7": ["logged"], "11.7 11.6 2.5": ["embrace"], "8.1 10.6 -6.5": ["bombings"], "5.7 1.3 -0.1": ["designers"], "2.1 4.1 2.5": ["pastor"], "-3.7 4.9 2.9": ["shutout"], "13.2 9.4 7.5": ["kicking"], "1.7 19.3 10.7": ["absolute"], "1.9 5.9 20.0": ["bone"], "12.1 8.1 6.9": ["upside"], "4.7 0.6 1.6": ["printed"], "15.0 -0.4 4.9": ["subsidies"], "4.4 5.2 -0.5": ["relation"], "-3.0 3.1 -6.2": ["reliability"], "3.5 10.3 0.3": ["eliminating"], "14.0 8.8 10.6": ["painted"], "7.3 10.1 8.6": ["mechanism"], "9.4 -0.9 14.2": ["sizes"], "4.0 8.3 6.1": ["define"], "0.9 10.0 8.3": ["outing"], "10.2 6.5 8.5": ["muscle"], "-1.8 2.8 -4.4": ["educate"], "2.4 7.3 14.3": ["boxing"], "8.9 7.7 -1.9": ["consolidated"], "6.0 9.9 2.7": ["intelligent"], "9.7 10.4 13.5": ["betting"], "25.6 13.9 10.2": ["legend"], "2.4 -1.3 2.9": ["outlined"], "-0.8 5.0 2.3": ["township"], "0.1 3.7 14.0": ["shuttle"], "-2.8 9.4 9.8": ["borrowing"], "5.4 12.4 1.5": ["barriers"], "3.5 11.8 1.7": ["theaters"], "0.7 7.0 -4.1": ["battled"], "15.4 9.6 13.7": ["snap"], "9.2 2.7 6.0": ["schemes"], "12.7 -2.4 9.0": ["prompting"], "17.2 18.8 -1.3": ["entity"], "6.2 -2.3 -5.3": ["breakthrough"], "7.2 5.9 -2.3": ["triumph"], "12.7 6.6 15.7": ["ton"], "9.2 10.0 5.2": ["clearing"], "9.3 13.7 8.3": ["minus"], "9.6 4.0 3.2": ["printing"], "13.0 12.5 -1.3": ["entities"], "1.0 10.2 3.3": ["trails"], "4.7 15.8 9.2": ["refugees"], "-1.1 22.9 11.7": ["excuse"], "-5.2 30.3 4.6": ["missions"], "0.2 3.3 9.9": ["apiece"], "8.3 4.1 2.9": ["celebrities"], "0.9 13.8 4.2": ["midfield"], "13.0 -0.7 7.9": ["chairs"], "2.1 15.2 9.3": ["rebuilding"], "0.9 5.5 5.4": ["sidelines"], "-0.8 8.7 5.1": ["tension"], "-3.6 14.8 9.5": ["electoral"], "3.4 6.3 2.9": ["invite"], "7.4 -0.6 2.2": ["disputed"], "17.6 6.4 -8.7": ["portable"], "-8.1 -0.0 9.5": ["tuition"], "2.8 22.0 7.8": ["intentions"], "11.3 9.9 2.5": ["app"], "17.4 -0.9 2.3": ["launches"], "9.7 8.8 3.5": ["refusing"], "-3.8 5.3 8.2": ["graduation"], "2.4 4.9 1.7": ["raced"], "8.5 6.8 -2.3": ["posed"], "10.5 18.2 5.2": ["ought"], "3.1 4.6 -1.4": ["publish"], "6.0 7.0 -2.5": ["securing"], "10.4 3.0 3.3": ["sole"], "2.9 3.3 14.2": ["couples"], "-0.2 6.0 1.8": ["clashes"], "-0.4 13.2 3.6": ["separated"], "6.7 17.8 8.8": ["breath"], "4.3 14.1 8.0": ["panic"], "13.8 6.4 11.7": ["elaborate"], "6.1 5.8 0.4": ["organizing"], "6.9 -2.5 8.4": ["mature"], "7.4 11.6 2.0": ["directions"], "4.9 5.7 7.9": ["meantime"], "9.1 8.0 -2.9": ["denies"], "-1.0 35.7 6.1": ["fighter"], "-7.3 9.2 -3.1": ["motivated"], "11.9 0.2 6.0": ["plug"], "15.1 -5.3 14.9": ["weighed"], "7.0 5.3 1.4": ["viable"], "3.9 12.6 6.6": ["harsh"], "6.8 16.1 9.7": ["bitter"], "0.3 5.4 5.9": ["reconstruction"], "0.5 6.0 3.8": ["assurance"], "-2.1 7.3 6.0": ["gender"], "10.2 15.8 17.4": ["spam"], "3.4 3.0 6.4": ["dose"], "-4.4 4.1 -1.2": ["supportive"], "7.5 0.7 -1.3": ["introducing"], "21.9 9.0 3.2": ["outfit"], "8.9 10.2 12.1": ["hat"], "23.5 0.4 12.5": ["slid"], "5.0 8.1 4.1": ["sacks"], "14.4 23.9 6.7": ["tanks"], "6.6 3.7 20.9": ["lottery"], "12.2 -2.0 19.5": ["tender"], "9.6 15.8 8.1": ["instant"], "10.6 20.1 6.4": ["stupid"], "8.4 5.9 0.8": ["interface"], "-2.6 8.3 -0.7": ["goalkeeper"], "8.7 77.9 9.0": ["enemies"], "7.5 -4.3 6.5": ["arranged"], "4.4 14.0 3.9": ["diplomats"], "1.0 15.6 1.2": ["deploy"], "9.0 6.0 9.1": ["youths"], "7.2 8.9 3.9": ["subsequently"], "-7.6 3.4 -5.0": ["contention"], "-4.6 -0.7 11.8": ["median"], "-2.6 9.2 -0.4": ["jurisdiction"], "3.4 9.9 9.8": ["burglary"], "8.2 2.6 11.0": ["slower"], "-0.2 9.0 -2.2": ["advantages"], "-2.2 5.9 23.8": ["wheat"], "6.0 7.2 1.6": ["worthy"], "7.8 14.8 3.7": ["shame"], "-0.0 14.5 -0.7": ["conflicts"], "19.2 11.2 0.1": ["quietly"], "1.5 -5.7 -1.3": ["benefited"], "-0.2 7.4 4.5": ["complain"], "9.5 22.6 12.2": ["inevitable"], "0.8 4.5 11.4": ["heating"], "12.3 19.4 1.1": ["desert"], "10.0 17.5 9.8": ["mountains"], "3.3 6.2 -2.6": ["internationally"], "0.6 15.3 -0.1": ["mosque"], "2.1 6.8 6.1": ["pressures"], "-2.6 4.0 8.8": ["ballots"], "10.5 12.3 12.7": ["occasionally"], "5.8 9.3 3.2": ["besides"], "8.3 1.2 0.4": ["turnaround"], "10.0 5.5 -0.9": ["concessions"], "4.6 9.2 0.1": ["remind"], "5.3 3.5 11.2": ["hip"], "2.1 5.7 -0.4": ["entertaining"], "5.7 14.1 5.3": ["willingness"], "-3.6 -1.2 7.1": ["episodes"], "1.6 24.5 -0.1": ["courage"], "4.8 5.3 4.3": ["shifted"], "5.4 15.5 7.8": ["foreigners"], "9.6 6.1 7.7": ["counterparts"], "-4.6 2.8 5.2": ["sentences"], "-3.5 5.1 5.1": ["merchandise"], "1.0 22.1 4.6": ["perceived"], "-1.5 6.9 2.5": ["satisfaction"], "0.1 3.8 -1.7": ["fulfill"], "0.7 24.2 0.9": ["defenders"], "8.6 14.4 1.1": ["silent"], "6.1 10.1 19.4": ["tourist"], "4.0 14.2 8.1": ["treaty"], "9.5 4.8 -0.2": ["holdings"], "10.2 11.5 1.7": ["adjacent"], "-1.8 8.3 8.3": ["applicable"], "3.3 10.3 13.6": ["bowling"], "-2.6 9.1 10.7": ["wicket"], "10.2 19.7 6.2": ["objects"], "-0.5 -2.3 6.8": ["applicants"], "4.7 8.4 2.5": ["freed"], "5.9 17.6 12.8": ["gonna"], "-2.0 2.0 6.7": ["layup"], "-0.2 10.9 10.6": ["bridges"], "1.1 1.9 -2.3": ["endorsement"], "-0.8 2.9 -5.0": ["examination"], "-8.9 4.9 -1.2": ["educated"], "0.1 5.5 6.2": ["tensions"], "9.6 15.7 -1.2": ["explosive"], "3.8 0.3 5.4": ["exceeded", "outshining"], "11.3 7.6 11.0": ["imported"], "1.8 17.6 10.5": ["fantasy"], "11.8 7.7 9.8": ["suits"], "1.0 3.0 -2.8": ["recognizes"], "13.2 4.0 3.9": ["m", "subcommittee"], "4.3 6.7 7.9": ["minimal"], "-2.1 15.3 14.5": ["medal"], "8.9 9.1 -0.9": ["reads"], "6.2 15.4 15.2": ["locals"], "9.0 8.0 5.1": ["trailing"], "-2.1 12.0 -1.8": ["prayers"], "2.8 4.5 7.2": ["v"], "1.8 12.2 6.9": ["suggestion"], "6.1 11.1 5.3": ["workplace"], "10.9 18.9 2.5": ["simultaneously"], "16.8 9.5 2.8": ["universal"], "16.2 2.4 18.0": ["lifting"], "4.6 -1.7 -0.5": ["financially"], "0.8 3.4 4.8": ["recruitment"], "10.5 19.2 6.7": ["quest"], "9.8 12.7 7.5": ["grave"], "14.6 7.3 6.2": ["lobbying"], "-2.4 6.8 -1.6": ["argues"], "14.5 9.5 0.5": ["bold"], "6.3 22.7 5.0": ["brutal"], "-5.2 13.8 -0.3": ["reply"], "11.6 -2.2 0.6": ["renowned"], "1.6 9.3 5.2": ["reconciliation"], "12.6 16.6 5.0": ["sleeping"], "9.5 2.7 5.7": ["computing"], "-0.1 14.8 7.4": ["sooner"], "3.3 4.6 0.3": ["switched"], "2.3 2.3 5.6": ["laptop"], "2.4 0.2 2.4": ["surveyed"], "-3.3 1.8 5.0": ["reservations"], "13.4 3.1 5.1": ["woes"], "-1.7 5.8 17.9": ["swim"], "16.2 5.3 2.7": ["marking"], "5.1 14.5 3.3": ["breathing"], "8.8 17.6 8.4": ["blind"], "6.4 22.7 3.9": ["immune"], "1.9 1.9 -6.3": ["founding"], "5.5 -5.0 4.1": ["opted"], "7.4 3.4 2.6": ["unrest"], "-3.9 1.6 0.3": ["curriculum"], "0.5 3.9 7.7": ["shifts"], "14.8 4.0 2.3": ["troubles"], "19.3 4.2 -1.9": ["distributor"], "12.0 14.2 -1.7": ["damaging"], "8.4 12.0 -0.1": ["coup"], "0.5 4.1 1.5": ["representation"], "3.2 7.9 -0.9": ["notify"], "12.9 8.1 -0.6": ["manufacture"], "10.9 9.1 9.5": ["random"], "-5.0 -0.9 3.9": ["institutional"], "-0.1 7.9 2.5": ["transported"], "4.1 3.8 17.2": ["protein"], "23.2 8.5 3.7": ["mounted"], "7.6 -0.5 6.2": ["bottles"], "-1.2 -4.1 0.4": ["presenting"], "6.0 16.4 8.1": ["pleasure"], "4.5 5.9 2.3": ["surveys"], "-7.0 16.5 4.6": ["accomplish"], "-2.5 9.0 4.2": ["declaration"], "12.5 2.3 3.6": ["dumped"], "10.4 -3.5 20.0": ["weigh"], "15.0 7.2 4.8": ["evolution"], "10.6 8.3 -3.8": ["accusing"], "11.4 3.7 -4.0": ["upgraded"], "2.4 10.4 16.6": ["teeth"], "16.3 9.0 4.2": ["lately"], "5.8 6.8 5.9": ["loses"], "12.6 11.5 5.1": ["browser"], "-4.0 14.5 2.1": ["politically"], "11.1 1.7 2.8": ["researcher"], "-0.5 1.6 7.4": ["leagues"], "-0.1 -5.1 0.8": ["subscribe"], "4.0 4.9 1.5": ["stabbed"], "0.8 -0.7 4.2": ["coupled"], "8.6 2.4 0.0": ["accessories"], "-8.1 9.9 4.0": ["accountability"], "10.3 10.3 1.9": ["setback"], "5.8 1.1 2.8": ["heels"], "-5.7 0.1 5.1": ["apartments"], "18.1 10.9 6.8": ["factories"], "-8.5 3.4 3.2": ["outcomes"], "9.8 -4.3 6.2": ["stalled"], "3.3 9.3 5.9": ["alarm"], "1.4 3.1 4.7": ["jumper"], "12.1 -6.9 6.5": ["centered"], "8.0 5.5 -4.5": ["integrate"], "7.8 6.3 4.7": ["advertisers"], "5.0 4.5 0.1": ["apologized"], "-1.2 19.6 8.1": ["unfortunately"], "11.0 7.0 22.8": ["chocolate"], "1.7 15.0 2.1": ["shootout"], "12.2 11.3 9.2": ["tale"], "5.9 1.8 1.0": ["finalists"], "12.1 13.3 34.2": ["marine"], "5.8 2.3 -0.8": ["flooded"], "-1.7 3.5 1.8": ["ethanol"], "10.4 11.2 7.2": ["tunnel"], "7.8 8.6 4.8": ["charts"], "-1.1 13.1 -0.1": ["accountable"], "1.1 -0.4 3.1": ["conclude"], "0.2 6.5 22.0": ["cook"], "2.2 8.2 4.1": ["conceded"], "7.4 13.3 12.0": ["stomach"], "1.7 5.2 0.4": ["enjoys"], "18.1 19.7 12.0": ["ugly"], "4.9 4.9 9.9": ["wrist"], "5.5 -0.8 6.3": ["clinics"], "-0.7 8.0 4.2": ["tally"], "4.7 6.9 5.5": ["arrives"], "0.3 7.9 4.5": ["volleyball"], "-0.1 10.4 5.9": ["drunk"], "-9.7 4.6 8.9": ["parole"], "7.4 6.3 3.6": ["spare"], "2.5 11.3 7.6": ["goalie"], "3.5 12.4 7.9": ["inability"], "3.5 -6.3 7.8": ["concerts"], "8.5 9.8 -3.0": ["liabilities"], "6.5 13.6 7.8": ["radiation"], "10.0 11.6 3.1": ["risky"], "-3.3 4.6 0.5": ["worn"], "8.8 7.6 6.8": ["inspectors"], "6.2 12.6 15.8": ["tag"], "-7.8 -5.6 1.7": ["enrolled"], "0.6 4.3 -6.1": ["convenient"], "2.6 8.3 1.3": ["amongst"], "11.1 2.1 1.6": ["exploring"], "9.9 23.2 4.6": ["dirty"], "4.7 14.2 7.4": ["unnecessary"], "4.6 5.0 2.7": ["guided"], "-0.6 8.4 7.4": ["volatility"], "11.1 0.1 17.5": ["pipe"], "1.1 4.6 12.3": ["unemployed"], "7.7 10.1 11.5": ["decides"], "-2.5 5.6 -4.3": ["inform"], "3.8 2.9 -0.2": ["disputes"], "10.4 2.8 2.6": ["institute"], "5.0 11.2 6.7": ["veto"], "1.1 -5.7 5.0": ["expired"], "5.0 2.8 4.4": ["issuing"], "0.6 -0.6 7.7": ["yields"], "7.4 1.1 11.4": ["fundraiser"], "14.7 2.3 -0.4": ["specialists"], "-1.5 -2.7 2.7": ["competed"], "5.2 9.2 6.3": ["implied"], "8.1 9.6 7.1": ["magnitude"], "0.4 -2.8 -1.3": ["comprised"], "2.5 9.6 7.1": ["keeper"], "15.2 15.2 1.9": ["aggressively"], "5.1 13.0 12.2": ["devastated"], "10.0 12.5 6.2": ["chasing"], "8.7 1.5 4.6": ["spends"], "11.3 4.8 5.7": ["graphics"], "7.1 9.3 24.7": ["cats"], "11.1 10.1 9.2": ["ridiculous"], "0.5 8.3 -0.7": ["affiliates"], "3.5 15.3 6.6": ["sellers"], "17.9 6.7 8.8": ["telecom"], "14.4 -8.8 1.0": ["sponsorship"], "5.7 2.7 6.6": ["supervisor"], "7.2 14.1 8.0": ["naturally"], "0.2 15.4 8.8": ["calculated"], "4.9 4.8 -2.2": ["publicity"], "15.8 1.6 2.7": ["slammed"], "-0.6 -2.9 -5.5": ["retained"], "7.1 -0.7 9.1": ["teenage"], "1.2 9.5 2.3": ["regarded"], "5.4 9.9 7.7": ["justify"], "4.6 19.7 3.5": ["radar"], "20.8 6.0 9.6": ["mounting"], "2.2 7.3 1.4": ["bathroom"], "4.4 8.6 -0.8": ["liable"], "20.8 7.5 11.9": ["climbing"], "0.8 4.0 11.5": ["substance"], "1.6 12.2 15.2": ["pets"], "8.2 -7.8 -1.8": ["oversee"], "1.4 7.1 3.6": ["trademarks"], "3.2 9.7 22.0": ["populations"], "-2.7 12.5 3.7": ["boundaries"], "8.2 22.9 2.0": ["gunmen"], "4.6 3.2 33.4": ["pot"], "17.9 1.1 2.8": ["dubbed"], "-0.8 10.8 0.8": ["enforce"], "27.0 11.2 11.8": ["beneath"], "8.0 9.0 24.7": ["ports"], "4.8 4.4 2.5": ["debts"], "4.5 17.3 0.5": ["advancing"], "-0.6 8.6 -1.0": ["adverse"], "1.1 12.2 -3.0": ["trusted"], "8.3 -6.8 9.9": ["caps"], "-1.9 10.2 0.2": ["flown"], "5.6 8.3 -8.8": ["kidnapped"], "0.8 10.7 3.1": ["declare"], "10.4 20.7 13.1": ["punch"], "20.1 4.4 17.2": ["pink"], "11.6 -0.3 10.7": ["tossed"], "1.7 -0.7 -8.0": ["affiliated"], "-1.5 8.6 33.4": ["harvest"], "28.3 -5.3 5.0": ["lucrative"], "29.4 -0.3 9.7": ["soaring"], "21.3 23.6 6.3": ["competitor"], "16.9 -0.6 -5.9": ["jointly"], "7.5 12.1 2.5": ["possibilities"], "13.4 8.5 6.4": ["commonly"], "-3.1 6.7 4.0": ["destinations"], "2.1 5.2 -6.6": ["stating"], "-6.7 0.9 4.7": ["pregnancy"], "14.9 6.3 9.4": ["experiment"], "14.5 38.7 3.2": ["hostile"], "1.1 10.2 5.7": ["expectation"], "7.6 8.3 5.9": ["indoor"], "5.1 -2.2 5.9": ["olds"], "6.0 9.0 8.5": ["spaces"], "11.7 11.6 4.4": ["firmly"], "-0.4 3.1 -2.9": ["passionate"], "10.6 8.8 6.1": ["taxpayer"], "-5.6 -3.3 1.1": ["collections"], "-4.1 24.4 3.5": ["sacrifice"], "6.4 6.6 2.9": ["basement"], "3.3 15.8 31.8": ["vessels"], "8.7 18.0 5.3": ["horror"], "19.5 13.7 15.3": ["drag"], "-3.1 4.8 3.1": ["visibility"], "2.7 17.9 -0.5": ["react"], "7.3 15.3 2.4": ["cooperate"], "-0.4 1.0 12.5": ["restoration"], "7.7 5.6 19.9": ["raw"], "10.4 8.1 13.1": ["grows"], "5.4 6.3 12.3": ["elbow"], "4.6 -0.3 7.1": ["entrepreneurs"], "8.6 7.9 5.4": ["describing"], "2.5 -3.4 0.7": ["conferences"], "13.2 10.1 5.5": ["aiming"], "8.9 7.2 -1.1": ["presidents"], "3.6 7.7 -1.8": ["belong"], "9.0 10.4 9.3": ["flags"], "8.7 0.5 7.6": ["semi"], "5.5 10.9 2.9": ["prohibited"], "-4.4 17.0 1.8": ["motivation"], "18.9 10.7 5.5": ["continent"], "-7.2 1.1 4.3": ["assessed"], "18.3 13.3 14.3": ["toy"], "9.9 9.2 -0.5": ["continuous"], "11.1 6.4 4.5": ["steadily"], "0.4 4.9 5.8": ["reserved"], "18.8 1.5 8.8": ["tops"], "-0.5 8.1 -4.8": ["efficiently"], "1.3 4.3 3.8": ["bureau"], "14.0 3.3 2.1": ["southwest"], "-7.9 1.0 10.5": ["weekends"], "-1.1 12.7 3.9": ["elimination"], "2.1 -5.7 -0.3": ["finalized"], "-0.3 1.1 -0.9": ["forthcoming"], "-0.1 7.9 10.7": ["lanes"], "18.9 6.7 9.0": ["dragged"], "1.0 2.3 3.5": ["refer"], "-2.9 16.1 5.6": ["emotions"], "11.2 6.7 9.3": ["ceiling"], "14.4 9.8 8.2": ["midst"], "16.6 5.2 5.9": ["beats"], "9.2 19.0 8.6": ["root"], "4.5 4.0 5.0": ["memorable"], "-1.8 8.7 5.9": ["determining"], "9.6 2.3 2.0": ["persuade"], "7.0 20.9 7.5": ["awful"], "3.8 12.6 15.3": ["seeds"], "11.1 8.8 3.5": ["logistics"], "2.9 2.7 -2.9": ["languages"], "6.0 6.9 -5.0": ["affiliate"], "-4.9 11.4 10.1": ["occurs"], "3.7 5.3 -2.2": ["connecting"], "10.3 0.5 -2.2": ["labels"], "7.9 9.2 5.1": ["grandfather"], "9.2 0.7 4.0": ["spark"], "14.3 3.1 -2.0": ["ripped"], "38.6 -3.6 13.3": ["sized"], "6.6 -2.2 6.4": ["marathon"], "4.7 10.7 6.1": ["planted"], "3.2 1.1 2.9": ["prospective"], "3.1 9.2 22.1": ["farming"], "10.1 0.8 5.6": ["tier"], "11.4 9.0 10.9": ["miners"], "3.5 9.5 18.0": ["farmer"], "3.8 5.4 1.1": ["proportion"], "0.6 16.7 35.9": ["deer"], "-2.5 7.1 4.8": ["detectives"], "16.6 10.6 -4.8": ["acquiring"], "7.1 12.0 9.7": ["cousin"], "4.0 15.1 9.2": ["cry"], "3.7 2.9 6.4": ["preparations"], "5.5 3.7 -4.8": ["upgrades"], "5.4 16.6 11.9": ["hill"], "17.2 4.3 8.3": ["warehouse"], "21.4 10.0 0.6": ["transform"], "12.1 7.4 -0.5": ["warn"], "-1.2 11.5 3.2": ["practicing"], "-6.8 11.6 1.3": ["campaigning"], "4.5 9.1 8.2": ["limiting"], "0.0 4.1 -0.0": ["teaches"], "4.6 3.3 5.3": ["stranded"], "2.1 5.3 7.8": ["b"], "-4.3 14.8 11.9": ["voter"], "2.8 -9.0 5.2": ["workshops"], "14.1 6.7 0.9": ["transformation"], "6.0 7.7 4.2": ["displaced"], "2.4 10.8 3.3": ["maximize"], "10.5 4.5 7.3": ["terrific"], "2.5 8.8 2.5": ["significance"], "17.6 1.6 9.0": ["outsourcing"], "0.7 3.5 -0.2": ["apology"], "-1.0 1.1 4.2": ["aired"], "18.8 1.6 2.9": ["exploded"], "17.4 19.9 6.3": ["fierce"], "-6.5 10.5 -0.0": ["contrary"], "1.1 18.0 1.8": ["unacceptable"], "-3.8 0.0 0.8": ["payable"], "2.1 9.8 4.7": ["progressive"], "2.4 10.6 6.4": ["anxiety"], "0.4 -6.9 7.2": ["scholarships"], "3.4 7.9 2.1": ["privilege"], "-2.8 13.4 7.6": ["catcher"], "7.1 2.9 -1.0": ["constructed"], "11.7 19.0 5.6": ["maps"], "-2.4 18.0 2.4": ["friendship"], "10.0 12.5 1.2": ["failures"], "9.5 -4.1 1.3": ["sounded"], "4.0 9.1 4.8": ["insist"], "2.3 2.8 3.9": ["applies"], "27.2 12.5 7.6": ["icon"], "14.8 11.0 7.2": ["phenomenon"], "6.4 10.0 3.1": ["succeeded"], "5.7 11.6 8.8": ["colleague"], "-2.0 6.8 -1.1": ["vocal"], "18.1 8.6 17.4": ["hook"], "5.1 -2.8 10.7": ["resumed"], "30.5 4.9 5.5": ["atop"], "-1.1 7.5 8.8": ["relay"], "0.4 15.9 6.7": ["execute"], "13.7 2.6 4.6": ["boosting"], "7.2 3.4 2.1": ["greeted"], "-1.3 3.4 3.5": ["relate"], "10.7 14.0 2.4": ["corners"], "2.5 8.6 19.8": ["fireworks"], "1.3 7.0 19.2": ["grain"], "-7.7 11.1 1.7": ["diagnosis"], "12.7 18.0 4.3": ["scary"], "13.3 3.1 2.2": ["southeast"], "-4.4 3.6 5.2": ["scoreless"], "17.6 12.4 3.3": ["toxic"], "3.0 36.7 6.7": ["missiles"], "-0.8 -0.6 7.7": ["shorter"], "4.6 17.4 6.7": ["mutual"], "11.8 11.4 11.2": ["forming"], "1.7 7.2 6.6": ["birdies"], "-7.7 5.0 11.6": ["varsity"], "9.7 9.8 29.7": ["bread"], "1.6 4.4 5.6": ["blogs"], "10.9 5.6 9.8": ["partially"], "15.5 1.5 17.3": ["cement"], "4.3 18.6 1.0": ["decisive"], "1.6 -0.0 -2.1": ["negotiated"], "12.8 7.3 19.8": ["feeding"], "6.1 16.4 2.9": ["toughest"], "3.9 5.0 2.1": ["consent"], "-6.5 12.5 3.8": ["undefeated"], "20.0 12.6 18.2": ["orange"], "10.5 -2.5 10.1": ["halted"], "1.6 3.6 12.1": ["paintings"], "14.3 5.8 4.3": ["automated"], "1.9 -0.2 -1.4": ["publications"], "-1.6 8.5 2.9": ["adjustment"], "9.2 -0.4 0.6": ["extends"], "-1.0 8.5 5.3": ["conscious"], "6.4 11.3 0.9": ["poorly"], "4.2 10.3 7.5": ["crying"], "6.2 7.9 9.4": ["genetic"], "4.9 7.3 8.0": ["sideline"], "6.0 5.5 17.2": ["cleanup"], "12.3 -8.6 0.7": ["specializes"], "2.4 2.0 13.5": ["lows"], "-1.8 -6.2 4.6": ["seminar"], "3.7 10.7 3.3": ["instrument"], "8.6 18.3 -5.0": ["dangers"], "3.0 7.8 7.7": ["columnist"], "-0.2 2.0 4.3": ["celebrations"], "4.6 11.2 9.7": ["floods"], "6.6 1.9 24.3": ["seasonal"], "-1.8 5.5 4.1": ["grounded"], "9.2 -2.2 2.0": ["consultants"], "1.2 8.9 5.0": ["journalism"], "12.7 4.4 9.7": ["petroleum"], "12.1 11.8 7.4": ["shifting"], "24.6 -2.2 5.4": ["soared"], "-0.1 7.4 -2.1": ["academy"], "0.6 -2.7 -1.5": ["owed"], "3.6 -2.0 -1.7": ["withdrew"], "-3.7 10.3 13.8": ["borrowers"], "-2.1 9.8 -0.2": ["interaction"], "-1.7 9.4 0.0": ["memo"], "8.7 5.5 5.8": ["flowing"], "3.4 7.8 8.0": ["confused"], "18.1 8.2 6.3": ["dominate"], "16.7 5.5 16.6": ["sank"], "-1.6 14.7 -2.3": ["loyalty"], "-3.9 5.7 11.6": ["diesel"], "-4.9 2.5 -3.3": ["encourages"], "9.9 1.1 3.4": ["courthouse"], "-0.2 21.7 -2.9": ["followers"], "6.6 5.7 3.7": ["rallies"], "5.2 4.1 3.5": ["robbed"], "7.8 1.2 -0.6": ["notably"], "10.9 3.2 -3.2": ["magazines"], "9.0 11.5 -0.2": ["embedded"], "-1.4 8.9 4.4": ["apologize"], "11.7 4.3 5.3": ["settlements"], "-6.1 2.2 5.3": ["sidelined"], "-1.9 7.5 3.1": ["indicators"], "7.4 13.7 8.4": ["lender"], "10.8 5.8 11.7": ["liquid"], "-2.2 -3.7 9.4": ["nutrition"], "-2.3 8.2 7.0": ["talents"], "7.3 -0.2 4.0": ["fits"], "5.2 2.4 1.6": ["preview"], "-0.8 1.3 -5.2": ["thanked"], "-9.0 1.0 6.6": ["turnout"], "7.1 6.6 4.5": ["ladies"], "12.4 4.1 1.9": ["outlets"], "21.8 -0.9 12.6": ["colorful"], "5.4 6.8 0.8": ["publishers"], "6.1 5.1 3.0": ["employ"], "-2.9 2.4 10.5": ["premiums"], "9.7 2.0 13.4": ["competitions"], "5.5 6.7 3.2": ["twenty"], "0.4 5.2 2.6": ["relieved"], "14.4 0.7 -1.8": ["suburb"], "4.4 8.6 8.6": ["birdie"], "-0.9 12.6 2.7": ["keys"], "6.2 2.1 -4.6": ["demonstrates"], "11.2 32.3 1.9": ["heroes"], "9.4 5.1 5.2": ["superb"], "6.5 12.1 2.5": ["gauge"], "-0.4 5.3 11.1": ["equities"], "14.6 12.8 11.3": ["automakers"], "14.7 5.7 1.0": ["courtesy"], "-4.5 12.5 -6.7": ["murdered"], "-1.3 5.1 9.6": ["disability"], "4.9 -0.4 4.1": ["halfway"], "1.8 9.2 7.1": ["anxious"], "4.3 11.7 12.0": ["strategist"], "2.3 21.9 5.5": ["strengths"], "-2.9 13.4 3.3": ["minded"], "5.3 1.2 12.9": ["mild"], "11.3 32.6 9.4": ["humanity"], "11.3 6.0 -1.7": ["manufactured"], "5.4 8.3 10.5": ["centuries"], "2.6 17.0 -1.7": ["supporter"], "11.9 1.0 -1.3": ["handing"], "-2.0 19.7 5.0": ["pray"], "2.6 -0.4 1.6": ["opt"], "7.7 14.3 8.2": ["screaming"], "11.7 3.2 39.6": ["cheese"], "4.7 6.3 -0.6": ["undertake"], "9.2 -2.0 0.4": ["combines"], "3.6 6.9 6.3": ["shoulders"], "1.6 14.3 11.0": ["severely"], "-2.1 6.7 -1.0": ["confidential"], "9.0 5.1 2.0": ["streaming"], "1.9 3.3 1.4": ["stakeholders"], "-2.8 5.8 7.8": ["recreation"], "9.9 -2.5 0.5": ["notable"], "15.7 5.4 5.9": ["peer"], "21.0 0.4 20.8": ["golden"], "9.5 12.3 25.1": ["bite"], "3.6 7.7 10.7": ["speeding"], "18.4 8.7 21.9": ["bears"], "14.0 19.7 17.4": ["deck"], "0.6 4.5 6.2": ["pupils"], "13.8 8.8 12.5": ["laying"], "5.4 -1.5 4.9": ["premises"], "4.1 13.9 1.0": ["detection"], "3.2 7.5 -1.9": ["searches"], "-3.2 6.6 4.9": ["caring"], "-2.5 10.7 3.4": ["profession"], "0.5 3.3 9.0": ["governors"], "3.9 14.2 12.8": ["hurting"], "-4.0 -0.2 -3.3": ["inquiries"], "5.3 9.5 -3.3": ["contender"], "-1.4 -1.1 8.0": ["relaxed"], "5.7 4.1 3.0": ["literature"], "2.8 4.4 3.7": ["charities"], "6.3 -1.1 2.1": ["discounts"], "4.8 9.6 6.2": ["historically"], "0.4 13.9 -0.8": ["travels"], "-1.6 6.8 31.6": ["bass"], "7.1 12.0 9.4": ["throws"], "9.6 5.8 1.8": ["stunned"], "2.9 15.4 8.5": ["minimize"], "8.1 16.6 -3.6": ["detect"], "2.4 15.8 6.9": ["patience"], "3.4 7.2 4.3": ["regain"], "5.7 6.6 1.6": ["detected"], "3.6 5.4 11.0": ["metals"], "-0.1 13.0 4.4": ["photographer"], "21.4 4.2 19.1": ["floating"], "11.9 9.8 3.3": ["showdown"], "0.6 9.5 5.2": ["chemistry"], "4.5 7.4 7.6": ["questionable"], "3.3 20.7 1.8": ["openly"], "12.8 4.1 2.1": ["holder"], "-1.8 8.5 9.3": ["impacts"], "2.1 7.6 6.1": ["pin"], "2.9 16.3 5.0": ["indicator"], "23.4 3.0 -1.6": ["watchdog"], "8.6 11.8 7.0": ["scattered"], "-2.3 11.5 9.4": ["rider"], "11.4 5.8 15.2": ["obesity"], "3.2 13.8 3.5": ["evacuation"], "4.8 24.9 -1.8": ["wherever"], "11.4 -6.7 9.9": ["wrap"], "2.3 4.1 1.2": ["reduces"], "12.2 -1.4 -4.3": ["commissioned"], "-6.2 1.8 3.5": ["albums"], "10.6 6.3 9.7": ["sticking"], "8.0 1.9 4.9": ["stretched"], "-0.9 9.4 19.8": ["cruise"], "4.0 10.1 7.8": ["tee"], "-2.2 15.9 1.2": ["associates"], "8.9 9.9 0.6": ["torn"], "8.5 16.7 5.2": ["ace"], "14.1 15.3 18.2": ["rocks"], "-0.1 6.8 6.0": ["styles"], "6.5 3.9 14.6": ["beds"], "0.9 21.1 12.3": ["mines"], "2.5 11.9 4.2": ["importantly"], "17.3 7.0 9.9": ["trademark"], "18.3 12.3 -3.9": ["blowing"], "10.4 14.0 1.3": ["hostage"], "-1.8 8.6 10.2": ["sewer"], "6.8 7.1 0.8": ["proving"], "3.3 2.9 2.1": ["develops"], "5.0 8.8 13.3": ["diluted"], "10.4 6.9 4.7": ["bolster"], "12.1 3.6 -0.7": ["patents"], "-3.6 7.1 -2.3": ["beneficial"], "-0.9 8.2 -1.4": ["credible"], "3.4 2.7 2.5": ["complaining"], "7.9 3.0 11.4": ["cooling"], "-2.6 5.6 1.4": ["nominees"], "9.4 5.0 6.3": ["transparent"], "14.1 0.6 1.3": ["erupted"], "2.2 14.3 5.6": ["receivers"], "0.4 -4.0 -0.1": ["undergo"], "-7.1 1.4 1.2": ["nominations"], "4.9 -4.7 -1.4": ["attracting"], "9.9 13.5 6.6": ["smell"], "2.4 0.9 3.3": ["considerably"], "6.1 -4.5 -2.9": ["contracted"], "-1.0 15.5 3.7": ["psychological"], "7.9 9.7 8.2": ["desperately"], "6.5 10.6 9.9": ["fingers"], "-0.6 8.7 3.3": ["remembers"], "6.5 10.1 4.6": ["aftermath"], "4.3 2.7 7.4": ["t"], "11.4 8.9 8.4": ["origin"], "6.0 -9.3 2.4": ["oversees"], "0.0 34.5 4.2": ["insurgency"], "0.3 7.9 2.2": ["podium"], "0.5 4.1 1.6": ["analyze"], "11.9 -4.4 -6.7": ["monitors"], "-5.7 0.5 -0.1": ["amendments"], "1.6 1.0 1.2": ["sum"], "12.4 6.2 21.3": ["mainland"], "1.6 19.8 7.8": ["hitters"], "3.6 6.7 -3.7": ["ousted"], "7.0 -0.8 12.3": ["mill"], "4.7 5.2 -0.9": ["citizenship"], "14.5 20.7 7.2": ["bloody"], "4.7 -3.2 -2.9": ["stint"], "5.2 18.7 4.5": ["ie"], "10.6 12.9 0.8": ["knocking"], "6.3 4.0 5.5": ["tenants", "titania"], "-5.0 -3.1 -3.1": ["supervision"], "-7.5 11.1 3.0": ["disagree"], "-2.5 13.3 4.6": ["regret"], "16.0 6.0 2.8": ["pact"], "12.0 9.4 14.1": ["brokerage"], "7.3 -0.2 1.7": ["starring"], "-2.1 -0.4 7.8": ["allocated"], "10.2 0.1 -1.9": ["celebrates"], "25.9 -7.3 -4.8": ["consortium"], "-0.2 22.5 9.3": ["abilities"], "10.9 13.6 1.2": ["reminder"], "4.3 -5.1 -1.9": ["inclusion"], "18.4 5.2 24.7": ["brown"], "7.1 3.6 9.8": ["haul"], "3.1 7.8 5.9": ["vs"], "-3.3 4.3 9.1": ["artistic"], "6.1 9.3 5.9": ["eventual", "biogenic"], "-2.0 1.0 3.9": ["flows"], "12.0 0.3 6.6": ["closes"], "7.6 9.8 3.1": ["structural"], "7.5 15.5 0.8": ["locate"], "8.8 15.5 6.8": ["unbelievable"], "6.3 14.8 2.6": ["thereby"], "0.5 9.1 4.2": ["assure"], "4.3 -3.3 5.4": ["satisfy"], "4.5 -13.3 2.6": ["presentations"], "2.8 -5.4 5.7": ["cancel"], "3.2 4.9 19.1": ["flavor"], "-1.0 4.1 17.9": ["ski"], "11.9 7.7 7.2": ["surprisingly"], "13.9 -2.0 6.4": ["tipped"], "-0.3 7.2 -1.9": ["strokes"], "-0.8 1.5 5.5": ["unhappy"], "9.1 21.6 5.0": ["communist"], "5.3 9.7 1.8": ["denying"], "0.1 0.7 2.7": ["influenced"], "0.5 -0.7 6.4": ["attendees"], "-4.1 5.7 5.2": ["shootings"], "12.7 17.9 7.2": ["beloved"], "9.6 8.1 -1.2": ["shocking"], "-2.0 11.8 2.6": ["recipient"], "-0.2 1.5 5.6": ["recipients"], "5.8 6.2 0.1": ["predecessor"], "8.8 10.2 0.3": ["warns"], "8.6 8.5 1.8": ["crashes"], "9.7 3.6 2.7": ["plagued"], "1.3 10.0 25.6": ["recipe"], "11.3 15.5 10.4": ["plain"], "0.9 10.5 2.0": ["whereas"], "9.7 12.3 4.6": ["routinely"], "3.3 5.8 -1.8": ["civic"], "-5.1 -8.3 1.7": ["appointments"], "-4.3 14.7 5.8": ["quote", "intersectionality"], "2.3 6.0 4.4": ["runway"], "-1.1 11.1 6.9": ["offenders"], "0.8 6.4 -2.5": ["investigator"], "-3.5 19.0 -1.4": ["assignment"], "1.0 4.2 4.7": ["inspections"], "-3.6 -3.4 -5.7": ["recruited"], "8.2 5.3 4.0": ["labeled"], "20.6 -5.6 -4.8": ["flagship"], "12.3 2.5 0.9": ["buzz"], "10.5 6.8 1.3": ["enters"], "0.5 8.9 -0.8": ["contenders"], "5.9 1.9 17.8": ["garbage"], "-0.6 6.4 6.4": ["borrow", "originators"], "-9.0 35.8 6.6": ["commanders"], "5.4 5.2 2.9": ["builds"], "8.2 3.4 7.7": ["rides"], "0.2 12.2 6.2": ["biological"], "0.9 15.4 8.1": ["emotion"], "14.7 4.6 5.8": ["commerce"], "15.8 -4.0 18.5": ["weighing"], "15.5 13.0 6.1": ["abandon"], "1.3 8.4 18.3": ["dining"], "6.3 -3.0 0.9": ["multimedia"], "13.2 7.3 13.3": ["occasional"], "6.0 4.9 17.0": ["casinos"], "11.4 -1.0 11.4": ["eased"], "5.9 21.5 14.7": ["phrase"], "14.0 14.2 6.0": ["demonstrators"], "8.9 12.7 27.3": ["islands"], "3.9 1.8 2.3": ["skeptical"], "-6.8 3.0 5.6": ["semester"], "5.4 11.3 11.0": ["rhythm"], "-2.2 -4.6 0.3": ["expire"], "-0.4 0.9 -3.5": ["accessed"], "3.6 14.3 2.9": ["undermine"], "4.8 19.7 13.2": ["mate"], "5.0 19.3 5.6": ["avoiding"], "6.9 15.4 7.1": ["weakened"], "10.8 -1.0 -2.4": ["boasts"], "10.2 1.8 8.3": ["contents"], "-4.5 1.5 15.6": ["pickup"], "6.8 11.0 5.2": ["pockets"], "-3.0 -1.6 1.9": ["renovation"], "9.9 8.8 4.2": ["grip"], "4.7 -3.8 0.9": ["certificate"], "11.0 6.1 2.8": ["combining"], "29.0 4.9 8.3": ["shaped"], "5.5 1.3 -0.6": ["promotional", "barred"], "17.0 2.1 0.2": ["fold"], "-0.9 -1.7 8.4": ["visa"], "1.0 11.8 2.5": ["reliance"], "12.1 9.5 0.1": ["scare"], "7.0 7.0 4.0": ["refusal"], "7.3 6.8 4.3": ["broadcasting"], "3.2 20.0 1.5": ["united"], "9.5 10.7 10.4": ["joked"], "6.9 7.3 2.6": ["switching"], "-10.9 5.4 10.9": ["freshmen"], "23.3 8.9 5.5": ["fortune"], "9.1 13.9 14.5": ["visitor"], "11.7 1.4 1.0": ["poured"], "-0.8 13.8 10.1": ["subscriber"], "-3.6 2.3 15.3": ["ounces"], "-7.4 6.8 0.0": ["touring"], "10.9 10.9 0.5": ["tear"], "1.2 7.4 8.4": ["bout"], "-0.4 10.1 -0.6": ["workout"], "-2.1 8.8 11.6": ["pants"], "2.9 3.7 -4.5": ["convenience"], "-3.2 -1.8 4.3": ["schedules"], "17.8 11.8 6.5": ["glory"], "11.9 23.0 10.9": ["trick"], "15.9 -6.2 8.1": ["panels"], "7.0 16.1 9.1": ["laughing"], "12.1 18.2 -0.4": ["seller"], "-6.3 -5.4 -0.5": ["evaluated"], "2.1 10.7 28.0": ["beaches"], "24.4 9.0 7.8": ["chains"], "5.5 7.7 8.8": ["predictions"], "9.7 5.2 4.8": ["sore"], "22.5 5.2 7.8": ["steep"], "2.7 8.5 11.6": ["jersey"], "8.3 9.1 -1.5": ["separation"], "11.8 17.2 12.7": ["mad"], "7.4 7.7 8.5": ["clip"], "-1.5 5.6 1.8": ["c"], "2.5 6.2 23.3": ["diving"], "-5.6 8.2 6.3": ["instruction"], "-3.0 7.5 5.7": ["amateur"], "13.3 7.9 15.8": ["anchor"], "13.6 -2.6 -0.6": ["placement"], "0.2 3.8 1.7": ["contend"], "5.8 9.4 6.3": ["bipartisan"], "1.7 8.5 3.3": ["wasted"], "0.4 8.5 -3.0": ["utilize"], "-1.5 8.8 4.9": ["limitations"], "-1.9 9.9 8.5": ["donor", "abusively"], "-3.2 15.5 4.7": ["likelihood"], "-3.8 21.2 5.6": ["confrontation"], "4.1 1.5 4.2": ["wondered"], "5.2 15.9 11.8": ["cure"], "12.1 0.1 3.4": ["upbeat"], "8.2 11.2 11.6": ["inner"], "2.5 12.4 4.1": ["pope"], "7.2 19.9 9.1": ["horrible"], "16.2 -0.4 17.2": ["aluminum"], "-1.9 -0.6 0.5": ["outreach"], "13.1 11.3 0.7": ["countless"], "8.7 7.2 5.0": ["distinct"], "1.1 11.7 11.3": ["skilled"], "1.3 16.3 -0.3": ["raids"], "2.0 4.2 0.6": ["needing"], "16.8 3.2 3.4": ["pence"], "0.1 6.6 -2.5": ["directing"], "7.6 1.7 10.9": ["ramp"], "2.0 3.9 6.7": ["info"], "7.4 9.4 5.2": ["separately"], "-1.1 1.7 -2.7": ["sacked"], "1.4 3.6 8.1": ["casual"], "2.8 11.9 0.4": ["quarterfinals"], "2.9 14.2 4.9": ["diplomat"], "13.2 -1.9 7.6": ["overturned"], "11.3 -1.9 12.4": ["partial"], "3.8 0.6 -1.7": ["advise"], "1.0 2.2 24.0": ["chef"], "19.5 2.6 12.3": ["pile"], "-3.0 6.9 2.6": ["editors"], "4.4 13.5 2.4": ["concentration"], "2.8 6.2 2.1": ["rewards"], "16.3 13.0 2.2": ["technological"], "8.5 14.2 13.1": ["console"], "-1.7 -1.0 -1.9": ["withdrawn"], "-3.3 14.6 7.4": ["worship"], "1.5 11.0 5.7": ["assuming"], "3.1 21.1 7.4": ["corrupt"], "6.8 9.4 4.3": ["cheer"], "10.4 2.7 4.1": ["catalog"], "8.5 8.8 7.3": ["habits"], "-1.8 3.2 -1.3": ["improves"], "13.0 -0.2 13.5": ["processor"], "11.3 2.4 11.6": ["sheet"], "11.9 -3.2 0.6": ["boycott"], "18.8 15.1 8.8": ["shadow"], "-9.2 12.6 3.9": ["homicide"], "3.6 5.2 -0.4": ["inspire"], "1.2 2.8 1.9": ["musician"], "4.4 13.2 3.2": ["interference"], "7.3 12.2 5.1": ["disposal"], "3.1 12.4 5.6": ["rivalry"], "12.2 13.5 -1.8": ["embarrassing"], "3.6 7.2 12.0": ["brokers", "tranquillizer"], "15.7 7.5 -2.1": ["banner"], "-7.5 2.9 -4.0": ["complications"], "3.6 3.4 -3.9": ["intensive"], "8.5 -1.3 -3.9": ["convincing"], "-2.5 1.8 5.0": ["borough"], "11.9 16.1 6.8": ["smiling"], "-9.9 13.0 2.8": ["trauma"], "0.0 9.9 6.7": ["kickoff"], "6.9 11.3 6.6": ["lawmaker"], "7.0 0.0 0.1": ["undergoing"], "21.6 6.6 -0.6": ["transformed"], "1.1 2.8 -2.0": ["evaluating"], "0.4 -0.8 0.8": ["lacked"], "-3.6 2.5 12.7": ["prescription"], "2.4 -2.3 -1.1": ["trustees"], "27.1 4.2 4.3": ["regulator"], "-2.0 7.5 -4.4": ["abused"], "0.1 14.0 1.5": ["committing"], "-0.5 -0.1 10.1": ["passport"], "-2.4 8.3 3.8": ["monetary"], "-1.5 1.5 1.1": ["pursuant"], "13.7 10.4 13.8": ["fragile"], "-0.9 9.4 0.5": ["header"], "9.5 3.5 4.1": ["apps"], "-2.8 10.9 4.2": ["instances"], "-5.1 17.3 -4.4": ["sworn"], "-0.6 5.5 11.7": ["chronic"], "15.7 3.5 9.8": ["twist"], "-1.6 9.9 7.3": ["medicines"], "3.3 2.7 9.5": ["inventories"], "6.8 3.8 5.8": ["blend"], "-0.3 3.7 7.1": ["anticipates"], "1.3 9.5 18.7": ["poker"], "17.1 13.4 10.4": ["machinery"], "0.5 23.9 2.6": ["revenge"], "4.1 9.3 7.3": ["shortages"], "8.9 19.7 18.3": ["bacteria"], "14.2 10.9 22.2": ["mud"], "-2.5 9.0 6.9": ["misdemeanor"], "0.4 5.3 1.4": ["fax"], "2.7 3.8 11.3": ["intact"], "16.2 9.7 10.7": ["weird"], "9.8 8.3 -0.4": ["swap"], "5.1 4.5 7.5": ["strained"], "6.0 10.5 1.9": ["creditors"], "21.8 13.1 5.5": ["insurer"], "7.0 14.5 6.0": ["dig"], "10.3 3.6 -3.8": ["posters"], "11.9 1.4 7.6": ["revive"], "-1.5 4.8 7.2": ["summary"], "-0.0 15.2 8.7": ["rhetoric"], "-1.3 1.3 2.4": ["recommends"], "7.8 -0.1 -0.5": ["associations"], "1.5 0.3 -3.8": ["exam"], "0.0 7.8 5.8": ["zoning"], "-1.6 2.4 10.7": ["vary"], "9.3 11.7 3.1": ["architect"], "-10.7 5.5 11.7": ["medications"], "-2.7 19.1 -5.0": ["defeating"], "11.5 10.1 9.2": ["flash"], "3.9 10.1 3.9": ["aggregate"], "16.4 9.8 6.3": ["naked"], "1.3 15.3 5.5": ["correspondent"], "4.0 15.4 1.6": ["policemen"], "3.6 14.3 7.9": ["uncle"], "1.4 -1.1 7.8": ["paperwork"], "20.0 9.7 10.3": ["patch"], "8.6 16.5 17.6": ["turf"], "12.7 5.8 10.9": ["counterpart"], "10.3 2.3 19.3": ["dip"], "17.8 6.9 9.5": ["tent"], "8.1 22.4 4.2": ["instantly"], "-1.4 5.8 11.9": ["cigarettes"], "-3.4 9.9 11.7": ["medals"], "-5.2 8.9 4.3": ["shortstop"], "19.1 0.9 5.8": ["buys"], "9.0 11.1 7.4": ["trader"], "2.6 5.7 3.2": ["coordinated"], "12.6 3.9 3.5": ["prepares"], "7.0 7.8 5.2": ["finest"], "7.9 -2.3 -4.8": ["announcements"], "-1.4 22.3 4.8": ["wounds"], "5.7 17.3 12.2": ["retreat"], "1.1 11.6 5.9": ["disorder"], "8.0 4.0 4.8": ["regulated"], "4.1 13.7 0.4": ["outright"], "10.7 -0.8 6.4": ["costing"], "1.2 4.3 2.9": ["settings"], "10.6 3.1 9.4": ["reversed"], "5.2 7.0 5.7": ["classrooms"], "6.5 -0.9 0.2": ["incorporated"], "2.4 5.7 -1.1": ["strengthened"], "-7.1 7.1 1.8": ["quotes"], "-0.8 27.3 5.7": ["shooter"], "10.2 3.2 5.2": ["bullish"], "10.4 4.8 5.2": ["plaintiffs"], "1.0 5.3 8.1": ["downs"], "4.9 6.7 1.2": ["themes"], "8.0 6.0 1.9": ["distributors"], "0.8 -2.1 1.4": ["revise"], "6.1 16.4 2.4": ["precisely"], "14.8 11.4 3.8": ["unidentified"], "-4.2 4.0 -2.8": ["exempt"], "6.7 19.3 2.8": ["gunman"], "3.3 8.0 14.0": ["immigrant"], "-1.7 2.3 10.3": ["municipalities"], "5.5 2.1 16.2": ["tissue"], "7.6 -3.6 4.5": ["sustainability"], "19.0 0.7 15.3": ["rolls"], "4.4 8.6 3.2": ["characteristics"], "7.9 3.3 -0.6": ["belonging"], "9.1 2.8 10.0": ["refinery"], "3.6 -0.6 -2.2": ["enthusiastic"], "-5.5 9.3 8.2": ["filming"], "4.1 3.8 2.9": ["capitalize"], "0.3 14.6 6.3": ["quarterbacks"], "8.4 10.1 27.9": ["bay"], "5.5 14.8 12.6": ["sake"], "9.1 13.3 4.4": ["correctly"], "-1.6 4.7 4.8": ["lacking"], "6.7 14.9 5.2": ["precise"], "8.2 -2.4 -2.6": ["linking"], "-0.1 11.9 1.6": ["practiced"], "4.7 9.2 6.3": ["creativity"], "-1.4 6.2 3.0": ["frequency"], "11.6 6.2 13.3": ["lovely"], "32.0 10.6 6.6": ["iconic"], "-5.7 12.2 1.1": ["recruits"], "7.0 15.7 11.2": ["woods"], "1.7 9.9 23.0": ["rivers"], "10.2 9.6 6.4": ["unlimited"], "1.5 -0.6 -3.9": ["libraries"], "4.5 12.3 -0.9": ["gates"], "-4.3 5.8 0.5": ["accomplishments"], "19.4 0.1 14.7": ["dipped"], "-2.8 9.3 3.7": ["lyrics"], "1.9 4.3 -2.7": ["connectivity"], "5.0 12.4 14.2": ["skipper"], "14.6 0.6 7.7": ["steam"], "2.9 15.3 10.9": ["divide"], "10.3 -1.3 6.4": ["x"], "9.0 4.5 14.2": ["stem"], "0.6 6.4 27.8": ["dishes"], "3.6 1.1 3.1": ["repay"], "21.4 9.2 12.8": ["animated"], "10.6 6.0 14.6": ["layer"], "6.2 7.0 -3.3": ["belongs"], "0.9 0.6 9.2": ["enacted"], "21.0 9.8 14.6": ["battered"], "8.0 -5.8 -3.9": ["teamed"], "0.4 15.4 5.4": ["confronted"], "2.8 9.8 9.7": ["genes"], "2.5 8.4 10.0": ["televised"], "0.1 7.7 6.7": ["relax"], "9.3 -0.4 -4.0": ["hailed"], "3.9 9.3 12.4": ["casting"], "7.1 2.0 6.1": ["hospitality"], "-2.0 0.6 -0.7": ["administered"], "1.3 0.6 2.0": ["rounded"], "5.2 4.0 14.3": ["fiber"], "9.5 2.3 14.6": ["folk"], "5.2 1.2 2.6": ["elevated"], "8.0 8.2 9.1": ["successive"], "0.7 -0.1 3.5": ["analyzed"], "4.0 13.8 3.8": ["lesser"], "3.7 1.3 -1.0": ["thorough"], "16.6 3.3 1.8": ["poster"], "11.6 5.6 2.1": ["studios"], "7.6 4.8 4.3": ["performer"], "5.5 4.3 12.4": ["pensions"], "7.3 4.8 2.2": ["assembled"], "13.0 10.1 13.1": ["ordering"], "4.6 9.2 2.0": ["bother"], "6.4 5.2 14.1": ["semiconductor"], "-0.2 1.2 8.5": ["consistency"], "12.8 3.3 26.2": ["cake"], "6.5 7.7 5.0": ["worrying"], "11.7 2.4 5.4": ["amounted"], "2.3 17.5 14.6": ["helmet"], "-3.3 12.6 7.3": ["marry"], "-3.6 7.9 3.4": ["obtaining"], "-3.5 5.9 6.7": ["uranium"], "-3.7 -1.3 9.1": ["dental"], "1.5 1.8 3.6": ["homered"], "3.5 3.3 2.8": ["tracked"], "13.0 5.5 6.7": ["wheels"], "12.2 8.0 7.4": ["altogether"], "4.1 18.4 5.3": ["exercises"], "3.7 5.6 4.8": ["favors"], "3.2 7.8 2.8": ["quicker"], "16.1 6.5 8.6": ["smashed"], "15.3 4.2 6.5": ["fixing"], "6.4 -3.6 20.9": ["dairy"], "-0.8 14.9 11.0": ["afterward"], "-6.9 9.2 6.0": ["scorer"], "3.6 6.8 7.2": ["photography"], "3.3 10.7 1.5": ["instructor"], "2.3 18.4 9.0": ["yelling"], "4.3 0.7 4.4": ["complement"], "-2.9 11.9 1.1": ["affidavit"], "3.8 9.3 0.2": ["disturbing"], "-4.9 8.5 0.7": ["murders"], "7.2 1.4 -1.1": ["compact"], "8.5 -3.1 -1.1": ["examining"], "13.9 12.3 10.9": ["threatens"], "-1.6 11.6 8.4": ["reflection"], "8.1 8.7 7.6": ["touching"], "4.8 6.2 8.6": ["shelters"], "4.0 9.1 1.5": ["proves"], "9.5 5.2 27.0": ["pizza"], "3.1 25.0 8.3": ["prisoner"], "5.1 5.5 14.8": ["diamond"], "1.4 2.2 -2.9": ["instrumental"], "6.0 4.9 3.0": ["copyright"], "5.7 1.7 4.9": ["lakh"], "2.4 16.2 0.2": ["uncomfortable"], "6.9 11.7 1.3": ["anonymous"], "19.5 5.6 10.6": ["crushed"], "6.6 27.5 3.5": ["brave"], "8.5 22.4 4.5": ["obstacles"], "2.8 1.7 20.4": ["juvenile"], "5.4 5.7 2.8": ["contingent"], "-3.9 2.0 5.9": ["merit"], "3.8 -6.5 2.7": ["voiced"], "4.8 3.9 5.3": ["clicking"], "0.1 0.2 9.9": ["piano"], "6.0 -0.6 4.4": ["stripped"], "3.2 14.8 4.5": ["adapt"], "2.6 6.2 -2.1": ["enhancing"], "3.7 13.3 6.8": ["romantic"], "1.6 7.4 -5.4": ["interact"], "5.1 13.9 11.5": ["blacks"], "3.9 0.4 4.8": ["webcast"], "-0.6 7.0 -0.9": ["speeches"], "7.8 -2.0 2.8": ["billing"], "3.8 12.6 10.6": ["ear"], "0.1 -2.1 0.2": ["composed"], "-2.9 3.8 8.1": ["convictions"], "3.7 15.4 11.5": ["cops"], "0.7 5.9 1.0": ["d"], "-5.2 7.3 3.9": ["interpretation"], "-2.0 3.0 -1.8": ["sang"], "-1.7 -1.6 -4.2": ["listened"], "3.5 13.5 13.5": ["inmate"], "-2.0 -0.3 2.5": ["credentials"], "10.0 7.0 5.7": ["domain"], "11.3 1.6 -1.8": ["imaging"], "2.4 4.5 6.0": ["disc"], "8.0 7.1 -1.1": ["poses"], "-1.2 13.1 6.9": ["healing"], "4.2 5.6 13.0": ["steroids"], "-5.8 0.0 -4.3": ["appoint"], "12.5 9.8 8.6": ["permanently"], "15.0 -1.2 0.8": ["agreeing"], "-1.7 2.8 2.2": ["outscored"], "10.6 4.8 5.0": ["cinema"], "7.2 9.8 3.5": ["photograph"], "8.7 3.3 5.8": ["heated"], "-2.8 -3.2 2.6": ["documentation"], "12.5 9.7 -5.1": ["leaked"], "2.7 -6.9 7.9": ["processed"], "0.2 -6.6 2.8": ["signatures"], "-3.6 4.8 3.8": ["differ"], "12.2 8.8 3.7": ["parallel"], "5.4 10.9 8.2": ["wash", "dawdle"], "1.1 -1.0 5.6": ["athletics"], "-4.3 5.7 6.5": ["editing"], "5.3 -1.6 -1.4": ["incorporate"], "-4.2 11.7 5.8": ["justified"], "3.3 17.1 2.1": ["racist"], "-3.4 3.1 4.1": ["observations"], "6.9 -0.2 19.0": ["migration"], "-1.3 -1.5 0.8": ["rehab"], "2.6 4.1 0.6": ["levy"], "7.4 9.3 8.6": ["stabilize"], "16.8 6.2 5.2": ["mechanical"], "4.7 14.1 8.3": ["precious"], "8.0 7.0 8.7": ["lowering"], "6.2 2.8 0.1": ["valuation"], "2.8 20.8 2.0": ["convoy"], "9.1 13.8 9.4": ["prosperity"], "16.3 14.2 9.0": ["lovers"], "17.7 1.2 2.1": ["booth"], "30.1 2.1 10.2": ["tumbled"], "2.3 10.9 4.3": ["forwards", "adequacies"], "14.9 -0.5 2.3": ["customized"], "2.4 8.7 8.8": ["highways"], "-2.4 12.7 8.0": ["dignity"], "1.6 13.0 11.8": ["tends"], "18.4 15.2 6.2": ["universe"], "6.3 6.2 6.0": ["infant"], "5.5 21.4 6.0": ["mates"], "2.3 10.7 51.2": ["fishermen"], "2.0 4.2 1.3": ["lacks"], "8.3 7.3 17.1": ["royal"], "5.8 3.6 8.2": ["accelerated"], "8.9 11.4 4.6": ["wary"], "-7.9 -0.7 -1.6": ["transfers"], "-2.9 3.6 5.0": ["impacted"], "4.8 9.8 4.5": ["spite"], "-3.0 8.8 1.3": ["conclusions"], "10.4 9.5 8.2": ["contaminated"], "20.6 12.3 3.8": ["bosses"], "3.5 0.8 1.5": ["promotions"], "10.5 19.7 7.6": ["resist"], "3.7 2.5 -1.0": ["undertaken"], "4.8 13.0 11.6": ["jokes"], "9.3 4.4 -4.7": ["embraced"], "-0.8 3.4 2.6": ["characterized"], "4.5 0.3 -0.4": ["dismiss"], "10.2 12.4 -4.4": ["batteries"], "4.6 5.7 3.3": ["suited"], "8.9 1.1 3.1": ["fitting"], "0.9 -1.5 1.4": ["lend"], "8.2 7.0 -2.8": ["misleading"], "-3.6 2.6 3.6": ["insights"], "5.5 13.7 -2.9": ["freely"], "0.1 2.7 5.0": ["shortfall"], "8.4 6.5 -3.0": ["tribunal"], "1.2 8.5 3.5": ["deficits"], "4.0 4.3 6.4": ["clearance"], "-6.3 6.2 2.3": ["assessments"], "-1.2 1.8 8.3": ["duration"], "7.4 2.7 13.2": ["accompanying"], "8.4 -2.7 1.5": ["standout"], "-2.0 12.6 2.0": ["surrendered"], "7.7 -6.3 3.7": ["slim"], "-3.0 5.3 -4.3": ["assisting"], "10.2 3.0 6.7": ["kit"], "0.9 16.5 7.2": ["genre"], "7.3 12.3 -5.7": ["abuses"], "5.2 10.0 1.1": ["overwhelmed"], "-0.1 1.1 4.8": ["documented"], "12.7 11.6 11.2": ["mirror"], "4.5 11.4 10.6": ["defenseman"], "4.6 12.4 5.8": ["dependence"], "5.0 3.4 14.0": ["portions"], "-1.8 2.6 15.7": ["recreational"], "7.9 7.7 6.7": ["consuming"], "8.2 10.2 9.1": ["breakdown"], "10.4 10.1 3.2": ["revealing"], "15.1 3.6 11.4": ["bust"], "-5.1 11.1 7.0": ["racial"], "7.3 7.3 8.1": ["predicting"], "2.0 9.1 3.0": ["timetable"], "18.2 6.7 21.9": ["wooden"], "5.1 12.0 3.3": ["encountered"], "12.5 17.2 2.1": ["imminent"], "5.1 1.4 -2.4": ["belonged"], "11.4 5.3 12.7": ["anticipation"], "-4.4 14.3 1.9": ["polling"], "5.7 -0.5 13.2": ["trim"], "16.0 2.8 0.3": ["sue"], "3.5 13.6 0.7": ["whilst"], "0.7 9.6 4.1": ["cemetery"], "5.2 3.2 -1.9": ["ultra"], "-0.8 0.3 1.8": ["deferred"], "8.4 14.6 5.0": ["chased"], "1.3 0.6 5.9": ["maturity"], "-4.1 13.5 3.7": ["mentor"], "7.1 9.6 16.1": ["pub"], "-0.1 11.0 7.6": ["bilateral"], "2.8 0.1 7.9": ["cycling"], "9.3 6.0 2.9": ["chiefs"], "6.9 1.6 1.8": ["injuring"], "0.2 22.3 7.6": ["flee"], "12.0 3.3 11.4": ["rebounded"], "0.9 19.7 10.0": ["ammunition"], "11.7 15.5 1.6": ["distant"], "22.7 -3.1 5.6": ["buyout"], "20.3 8.4 8.6": ["circles"], "-6.4 6.0 4.9": ["fares"], "9.0 18.9 7.8": ["secrets"], "1.4 0.8 -5.9": ["expressing"], "12.5 3.0 -0.4": ["niche"], "12.5 5.4 15.4": ["toss"], "-0.9 15.4 7.4": ["constituents"], "7.3 5.6 6.8": ["compares"], "14.8 18.8 6.1": ["nightmare"], "3.9 30.3 7.6": ["rockets"], "4.0 12.1 11.5": ["priest"], "-2.3 1.5 1.9": ["expenditures"], "4.9 8.0 9.3": ["oxygen"], "6.9 -3.3 8.4": ["suspend"], "5.2 8.9 7.9": ["preference"], "6.8 10.2 6.6": ["inadequate"], "5.5 3.8 -4.2": ["confirms"], "0.4 15.1 2.9": ["refrain"], "18.2 14.4 -11.8": ["revolutionary"], "5.9 18.9 15.4": ["hunger"], "8.3 12.2 -2.9": ["controller"], "16.2 0.2 1.5": ["scam"], "5.8 -1.6 11.4": ["easing"], "-2.0 0.4 2.7": ["booking"], "3.9 5.0 2.4": ["rode"], "-3.6 8.6 21.3": ["livestock"], "11.4 16.3 8.3": ["habit"], "1.4 6.7 -2.1": ["functioning"], "15.1 4.7 2.8": ["signaled"], "5.6 3.3 6.5": ["deliveries"], "10.4 4.6 11.2": ["penny"], "18.7 8.6 12.7": ["slash"], "14.2 15.4 13.7": ["backyard"], "11.5 18.0 11.3": ["villagers"], "4.0 7.3 5.4": ["wounding"], "2.1 24.7 5.7": ["surrender"], "-3.0 -2.2 2.8": ["accommodation"], "2.1 13.9 33.4": ["dish"], "11.9 0.7 2.1": ["regulate"], "6.0 3.1 3.9": ["predicts"], "-0.6 -3.1 1.8": ["performs"], "-0.8 -3.5 10.0": ["netted"], "-1.4 3.6 17.1": ["liquor"], "11.0 -8.5 4.6": ["handles"], "1.1 5.1 7.3": ["judged"], "-2.9 -0.6 -1.8": ["oral"], "-1.1 8.7 4.7": ["drilled"], "2.4 7.9 4.4": ["relying"], "8.6 2.7 8.5": ["modified"], "6.1 4.2 7.5": ["suburbs"], "2.9 14.4 2.5": ["tornado"], "13.5 29.4 1.3": ["destroying"], "6.4 2.7 10.4": ["washed"], "0.3 4.8 1.4": ["hurdles"], "8.4 33.3 0.8": ["spy"], "15.7 1.1 5.9": ["bizarre"], "13.1 7.0 5.1": ["shook"], "-0.7 -1.7 4.6": ["reopen"], "-5.5 3.4 -0.5": ["unanimous"], "15.8 28.7 6.2": ["invisible"], "17.7 4.7 6.1": ["meltdown"], "0.2 -0.8 5.9": ["protocol"], "7.6 5.3 4.7": ["derived"], "-1.7 12.6 0.1": ["coordination"], "4.1 6.0 15.9": ["dam"], "1.5 1.9 6.0": ["councilors"], "18.1 4.0 7.3": ["twin"], "10.8 8.2 12.4": ["scratch"], "13.2 15.2 5.6": ["navigation"], "-1.6 -1.2 -2.4": ["monitored"], "8.0 18.5 5.8": ["airplane"], "17.4 6.0 10.6": ["lure"], "-3.6 2.1 9.2": ["doses"], "-0.2 1.7 -2.6": ["verify"], "9.7 11.9 10.0": ["bloc"], "3.7 10.4 8.9": ["okay"], "5.8 21.1 8.4": ["fleeing"], "4.8 5.9 4.7": ["ethical"], "9.4 9.4 8.5": ["consumed", "nostalgists"], "5.7 -0.7 8.9": ["pharmacy"], "7.7 12.3 9.4": ["brush"], "8.0 -5.7 4.0": ["upheld"], "1.9 10.6 8.2": ["traditions"], "6.3 17.9 6.5": ["ears"], "-1.7 9.0 -0.9": ["intercepted"], "-1.6 -4.6 -1.9": ["expires"], "3.0 18.0 2.2": ["faithful"], "3.0 0.5 4.1": ["renew"], "7.4 16.8 3.3": ["believing"], "1.3 9.2 -7.1": ["raped"], "7.4 7.4 6.4": ["digs"], "-1.2 9.7 5.9": ["punt"], "3.3 13.7 11.7": ["submission"], "2.2 9.4 8.2": ["desired"], "3.2 8.2 16.0": ["bones"], "0.8 2.8 6.1": ["metro"], "-1.4 24.5 3.1": ["insult"], "4.3 3.9 3.3": ["receipt"], "5.0 6.3 2.2": ["existed"], "1.0 0.7 3.8": ["organizer"], "5.4 7.9 8.1": ["concentrated"], "5.8 10.0 10.0": ["spectators"], "7.2 8.2 9.6": ["nationals"], "8.1 16.7 6.9": ["persistent"], "18.9 7.0 2.2": ["portal"], "-6.0 2.3 9.1": ["averages"], "12.9 -6.9 0.4": ["overseeing"], "2.5 1.6 0.0": ["appliances"], "10.2 4.1 -0.5": ["naming"], "12.6 4.4 13.7": ["mixture"], "8.9 9.2 8.0": ["rebounding"], "-5.7 2.0 4.8": ["dismissal"], "3.3 13.7 11.8": ["cultures"], "1.9 -0.5 6.3": ["staffing"], "-0.5 4.8 3.4": ["debates"], "0.6 20.9 9.5": ["bullet"], "1.9 2.1 1.7": ["disruption"], "2.4 20.8 13.3": ["sovereignty"], "6.6 5.5 5.3": ["clubhouse"], "1.3 4.0 1.3": ["confessed"], "6.0 3.2 -3.9": ["functional"], "3.0 5.1 -0.5": ["urges"], "16.0 5.1 -1.6": ["blasted"], "19.1 6.8 15.1": ["candy"], "3.7 7.9 0.2": ["feat"], "-3.0 5.7 -1.5": ["indications"], "1.3 4.2 3.9": ["unaware"], "16.7 5.9 0.3": ["installing"], "-4.3 2.3 6.5": ["fouled"], "7.6 18.7 7.3": ["angle"], "1.9 3.5 -5.0": ["objections"], "-6.9 -0.3 12.4": ["incomes"], "12.2 8.2 5.0": ["generic"], "4.0 5.5 1.4": ["solicitation"], "8.3 0.4 5.1": ["proposing"], "7.8 2.2 6.9": ["curious"], "19.5 4.6 6.3": ["bankers"], "8.6 7.2 10.3": ["contestants"], "1.9 8.1 3.9": ["prisons"], "8.3 5.8 9.0": ["squeeze"], "6.1 20.3 9.6": ["gangs"], "5.9 3.8 -6.6": ["compatible"], "7.1 17.2 12.9": ["tribe"], "2.3 2.1 7.2": ["propose"], "20.8 6.4 5.9": ["smallest"], "4.7 13.5 10.2": ["wisdom"], "11.0 6.5 23.3": ["container"], "2.5 12.0 4.1": ["blessed"], "1.9 14.4 -0.9": ["activated"], "4.6 3.8 -1.8": ["eve"], "11.9 -0.8 10.4": ["spike"], "5.2 4.1 9.7": ["councils"], "-0.0 7.6 -0.2": ["owe"], "7.1 1.0 2.9": ["earliest"], "5.2 7.5 3.7": ["winger"], "4.9 9.4 15.0": ["census"], "11.7 4.6 4.8": ["pumped"], "12.0 16.6 19.1": ["wings"], "4.2 -1.6 -5.0": ["promotes"], "9.0 17.8 3.7": ["continually"], "1.6 17.0 4.1": ["incoming"], "19.7 10.7 1.9": ["beside"], "-1.7 -1.4 -2.6": ["endorse"], "8.2 -3.7 3.4": ["spur"], "-1.8 10.8 6.1": ["cornerback"], "5.6 14.5 9.5": ["spirits"], "11.2 1.2 4.7": ["evolved"], "-3.5 9.3 1.1": ["threshold"], "-4.4 0.0 4.2": ["minors"], "0.4 12.1 2.5": ["qualities"], "21.4 7.8 7.0": ["backdrop"], "14.3 7.2 21.7": ["rig"], "7.7 10.6 10.3": ["bets"], "2.9 4.7 8.2": ["informal"], "1.1 7.2 3.9": ["rewarded"], "6.0 9.5 11.1": ["protective"], "4.3 6.2 -2.1": ["recognizing"], "1.7 6.1 3.7": ["urgency"], "2.9 15.0 7.3": ["handset"], "8.1 9.0 8.0": ["boot"], "10.7 1.9 0.7": ["hottest"], "-2.9 21.9 4.3": ["partisan"], "6.6 3.1 6.5": ["shutdown"], "0.2 6.3 3.7": ["ceremonies"], "2.8 -0.1 5.3": ["journal"], "7.3 9.2 -4.4": ["independently"], "-3.7 3.6 13.6": ["kindergarten"], "0.8 3.3 12.7": ["chipped"], "12.7 8.2 3.1": ["amortization"], "7.1 16.2 2.2": ["critic"], "8.0 13.6 11.5": ["blessing"], "1.2 3.3 14.5": ["cotton"], "4.4 7.2 9.8": ["procurement"], "14.6 11.4 12.8": ["silly"], "4.9 20.7 2.4": ["deliberately"], "4.6 4.3 -1.7": ["violates"], "10.4 1.3 -0.3": ["tapped"], "8.1 7.7 0.8": ["insisting"], "11.1 3.8 2.7": ["uncovered"], "11.1 -2.0 -3.5": ["alleging"], "21.4 19.7 10.1": ["epic"], "5.8 8.5 19.2": ["blues"], "8.2 5.7 12.1": ["merchants"], "-0.7 -1.0 3.1": ["concludes"], "-2.4 11.2 2.8": ["punished"], "9.1 7.8 5.5": ["complexity"], "25.7 -2.2 -2.7": ["pioneer"], "5.7 0.1 11.3": ["dancers"], "9.7 2.6 -6.7": ["financed"], "9.7 4.2 9.8": ["fabric"], "2.9 5.2 15.6": ["bicycle"], "5.6 2.9 4.1": ["references"], "2.1 13.1 16.6": ["forests"], "1.9 13.6 4.9": ["infections"], "1.6 -1.1 -1.7": ["collaborative"], "-2.0 7.9 -0.2": ["regards"], "10.4 4.2 7.9": ["albeit"], "24.1 7.4 7.1": ["dominance"], "2.1 10.0 3.5": ["uniforms"], "4.1 9.9 9.9": ["patrons"], "14.9 17.6 6.8": ["nasty"], "4.0 5.7 6.5": ["restart"], "13.9 16.6 3.5": ["dawn"], "13.2 11.6 8.4": ["wiped"], "6.4 22.3 3.0": ["holy"], "0.0 -2.1 6.4": ["renewal"], "13.2 -1.0 13.5": ["slashed"], "18.2 6.4 13.9": ["plunge"], "9.8 6.5 3.0": ["identical"], "2.7 12.4 -0.7": ["manual"], "1.9 6.4 13.8": ["comic"], "2.3 12.7 8.2": ["prone"], "-2.6 10.7 6.3": ["gaps"], "1.8 10.9 3.6": ["refers"], "10.1 10.5 -0.4": ["declaring"], "5.5 1.6 4.7": ["nod"], "-3.8 2.2 12.2": ["allocation"], "6.7 4.5 15.5": ["autumn"], "8.2 4.9 10.4": ["shoe"], "1.8 3.2 -1.8": ["alerts"], "1.4 7.8 8.3": ["fundamentals"], "1.8 2.3 0.8": ["exemption"], "5.2 11.2 8.1": ["thoroughly"], "13.1 -0.6 4.7": ["vibrant"], "8.2 22.8 3.4": ["hostages"], "4.4 5.3 0.1": ["successes"], "5.7 11.1 5.1": ["tackling"], "4.0 10.0 3.6": ["repeal"], "0.6 0.8 3.5": ["ranch"], "-13.0 6.4 3.7": ["absent"], "10.7 3.4 13.9": ["zoo"], "2.4 16.7 -2.4": ["genocide"], "8.9 4.7 5.1": ["mum"], "11.9 6.9 15.5": ["lawn"], "0.6 9.5 4.7": ["tense"], "-0.9 17.1 2.0": ["motive"], "4.0 8.8 4.8": ["cooperative"], "20.2 6.2 10.0": ["bubble"], "13.5 11.5 8.9": ["attraction"], "15.5 2.2 10.6": ["overweight"], "0.7 2.4 -0.1": ["analyzes"], "-2.3 13.3 -2.0": ["pursued"], "-0.9 6.2 3.2": ["statute"], "2.4 17.5 7.9": ["surviving"], "-3.0 10.5 4.4": ["bleeding"], "4.7 0.3 -0.1": ["alerted"], "8.2 17.4 6.0": ["jets"], "10.4 15.3 2.6": ["exploit"], "18.6 9.8 7.2": ["measuring"], "10.1 10.4 8.0": ["mount"], "0.3 5.0 6.3": ["supervisors"], "13.5 10.5 8.4": ["shaking", "agrochemical"], "30.8 -2.7 12.5": ["booming"], "0.7 3.9 5.6": ["alumni"], "-5.9 15.0 2.9": ["mentally"], "8.0 3.6 4.4": ["floors"], "3.3 5.9 14.1": ["builders"], "-2.1 -0.4 -5.5": ["echoed"], "-1.0 1.4 2.1": ["disabilities"], "-7.5 5.3 9.8": ["tallied"], "1.7 7.0 0.4": ["circulation"], "7.8 24.5 4.9": ["whoever"], "0.4 9.1 7.0": ["valley"], "12.2 -3.9 14.7": ["yearly"], "6.9 6.5 4.3": ["railway"], "7.1 9.1 3.0": ["arguably"], "17.8 6.3 21.2": ["rubber"], "4.1 9.8 5.4": ["endured"], "-0.9 6.9 3.0": ["instructed"], "17.5 14.7 10.1": ["underneath"], "15.8 18.1 4.0": ["supposedly"], "13.8 -3.7 0.7": ["leases"], "-4.3 5.0 -0.1": ["ensures"], "-9.1 19.0 -2.6": ["assassination"], "10.0 9.7 -4.1": ["blasts"], "6.3 19.5 9.5": ["logic"], "-0.9 3.6 2.3": ["outgoing"], "7.5 11.2 8.2": ["laughed"], "4.2 11.4 6.5": ["cellular"], "7.5 0.3 9.6": ["unrelated"], "12.0 10.6 14.3": ["imposing"], "1.6 28.0 2.0": ["confront"], "-1.1 1.0 7.2": ["hamstring"], "9.8 9.3 14.4": ["sack"], "5.9 30.4 6.5": ["defenses"], "15.1 7.1 1.1": ["diversified"], "7.7 11.6 -2.3": ["wrongdoing"], "6.6 1.4 16.5": ["scrap"], "4.2 8.3 9.1": ["gene"], "12.6 17.7 10.8": ["knees"], "-1.4 6.0 10.6": ["siblings"], "4.7 3.5 -0.4": ["expenditure"], "5.9 12.5 2.9": ["concepts"], "-12.1 3.8 18.8": ["wines"], "-6.9 6.0 16.7": ["foreclosures"], "0.4 -5.1 -1.0": ["profiles"], "4.5 5.3 14.4": ["glove"], "6.9 2.4 5.2": ["settling"], "4.6 10.4 2.9": ["incurred"], "2.9 7.4 5.0": ["twelve"], "6.4 -1.0 -7.5": ["forefront"], "3.1 17.2 4.4": ["racism"], "7.1 6.6 2.9": ["overcame"], "5.5 17.2 6.4": ["imagination"], "3.2 7.4 13.9": ["cigarette"], "3.8 4.4 -0.9": ["privately"], "2.4 5.0 2.7": ["adopting"], "7.7 9.2 -2.8": ["scan"], "6.1 7.1 15.8": ["lean"], "-1.3 0.2 0.6": ["lecture"], "3.7 8.4 11.4": ["wreck"], "1.3 13.9 16.7": ["planting"], "5.7 7.3 5.8": ["alter"], "-3.0 1.1 -1.9": ["graduating"], "14.5 -4.0 6.2": ["stellar"], "15.9 20.5 12.6": ["overhead"], "5.6 7.9 7.9": ["glasses"], "0.7 10.6 9.1": ["customs"], "14.6 1.0 -0.9": ["banning"], "-2.0 14.1 0.9": ["harassment"], "2.2 3.1 5.2": ["apparel"], "22.0 9.1 17.9": ["colored"], "9.2 10.5 7.1": ["grace"], "3.8 5.9 2.6": ["unsuccessful"], "-4.0 20.4 -0.1": ["stationed"], "8.4 33.1 3.1": ["attackers"], "10.2 7.7 2.1": ["measurement"], "8.2 12.4 21.1": ["males"], "8.7 3.1 15.4": ["containers"], "6.8 9.3 5.8": ["automobile"], "4.6 2.1 10.2": ["skip"], "12.9 4.7 17.1": ["bronze"], "10.8 -3.5 6.6": ["revival"], "-4.5 16.6 -2.6": ["distinction"], "-0.8 13.5 5.2": ["detective"], "13.9 14.6 23.6": ["sinking"], "3.0 0.3 9.4": ["baskets"], "-2.0 4.3 3.0": ["resolutions"], "1.7 2.4 -5.2": ["distinguished"], "3.4 3.0 2.6": ["translate"], "19.7 7.5 5.9": ["superstar"], "8.7 -5.0 3.5": ["consisting"], "6.1 18.7 13.1": ["cop"], "18.1 7.2 12.1": ["dump"], "7.9 15.4 13.1": ["sequence"], "3.1 7.3 9.0": ["calories"], "8.6 -2.6 16.1": ["processors"], "13.8 10.9 22.2": ["tail"], "-2.3 7.9 1.2": ["intervene"], "14.7 11.8 9.3": ["swinging"], "13.3 7.5 2.6": ["outlet"], "8.9 17.8 -1.1": ["explosions"], "-15.8 14.9 12.2": ["firearms"], "13.5 -8.7 1.1": ["specializing"], "3.7 9.9 18.4": ["breed"], "-8.1 9.9 8.8": ["receptions"], "5.8 2.2 13.3": ["healthier"], "-2.7 2.9 7.4": ["educators"], "1.1 -0.2 1.3": ["excluded"], "5.1 7.5 11.5": ["strictly"], "-0.8 -1.2 -2.0": ["inception"], "7.2 3.7 3.5": ["restrict"], "0.9 2.7 7.2": ["p"], "0.2 -0.6 2.9": ["laptops"], "5.2 -4.4 3.5": ["refund"], "15.1 2.7 -5.1": ["designing"], "19.0 5.0 9.6": ["looming"], "4.7 14.5 9.2": ["stockholders"], "1.0 13.8 7.6": ["alternate"], "0.3 -2.3 11.8": ["purse"], "-0.1 2.5 8.6": ["varied"], "11.4 -3.7 -3.6": ["surfaced"], "0.5 12.9 0.2": ["secular"], "7.2 24.9 10.3": ["ours"], "7.0 -0.9 9.1": ["lighter"], "12.7 6.9 2.3": ["construct"], "16.9 9.9 1.0": ["lit"], "11.9 1.5 19.9": ["ate"], "1.3 7.8 0.7": ["sensitivity"], "10.0 12.5 5.8": ["refuses"], "-5.4 4.7 6.6": ["correction"], "-0.8 1.8 17.7": ["recipes"], "4.9 13.2 11.8": ["toe"], "-2.7 7.2 11.5": ["allowance"], "5.2 9.0 5.5": ["attitudes"], "-5.8 6.2 6.5": ["occurring"], "16.3 0.4 7.6": ["aerospace"], "2.6 -1.4 0.1": ["clinched"], "4.1 4.8 2.7": ["hander"], "-1.8 17.4 3.6": ["honestly"], "6.7 6.1 1.6": ["derivatives"], "8.3 1.1 4.4": ["stemming"], "6.3 -3.3 -3.3": ["unanimously"], "8.2 7.4 6.8": ["fixture"], "-6.0 4.1 -0.4": ["therapeutic"], "16.0 5.0 9.4": ["sluggish"], "15.9 12.9 17.5": ["sticks"], "13.2 1.4 2.8": ["sciences"], "2.1 2.5 4.9": ["commissions"], "13.6 8.4 5.4": ["pumping"], "-5.3 11.9 2.5": ["possessions"], "0.7 7.0 26.6": ["ferry"], "66.1 6.8 7.9": ["giants"], "15.0 5.3 2.4": ["dominating"], "2.6 9.8 2.2": ["mobility"], "11.9 14.9 10.2": ["congressman"], "-2.2 0.9 -0.2": ["additions"], "11.4 6.9 0.4": ["codes"], "5.2 7.8 3.8": ["petrol"], "8.2 12.6 8.4": ["competitiveness"], "1.5 2.0 1.6": ["disappearance"], "9.3 8.6 1.9": ["seize"], "4.1 3.9 1.6": ["slaying"], "-0.8 -6.8 4.3": ["reopened"], "-2.2 5.4 -1.2": ["respects"], "9.8 6.3 18.5": ["brick"], "11.3 2.9 10.3": ["shelf"], "5.1 8.8 5.8": ["password"], "0.0 14.3 1.7": ["intimate"], "2.1 8.9 6.6": ["bias"], "7.7 3.7 5.8": ["shine"], "10.4 4.9 8.1": ["rings"], "5.1 3.1 -0.3": ["forums"], "12.6 14.4 13.1": ["laser"], "8.3 16.5 0.7": ["unlawful"], "-3.8 9.4 2.6": ["thankful"], "11.8 2.4 -0.4": ["demonstrating"], "4.4 12.6 4.7": ["romance", "yogic"], "11.7 12.5 10.0": ["smuggling"], "12.4 -3.7 -2.4": ["housed"], "9.5 -8.0 12.3": ["moratorium"], "9.8 4.7 -0.8": ["pivotal"], "8.9 1.4 12.9": ["pipes"], "5.3 11.0 0.9": ["namely"], "11.3 5.1 10.6": ["beverage"], "1.1 13.9 7.6": ["denial"], "7.9 11.4 3.6": ["sights"], "6.2 -2.1 9.5": ["stamp"], "15.5 6.8 4.8": ["owning"], "-4.2 -2.8 4.7": ["issuance"], "8.4 4.6 -1.7": ["inviting"], "-3.0 9.8 2.3": ["contributor"], "1.8 0.1 6.6": ["cleaned"], "9.4 15.3 23.9": ["tide"], "-2.8 3.0 -3.9": ["consult"], "-3.2 7.2 5.8": ["observe"], "-0.3 4.3 -0.7": ["emails"], "3.8 5.4 5.4": ["relies"], "5.8 12.7 11.9": ["boots"], "6.5 15.1 28.8": ["habitat"], "0.6 3.6 1.5": ["reservation"], "-0.1 1.9 10.4": ["parish"], "-3.8 12.6 9.1": ["runoff"], "8.4 1.1 4.3": ["prompt"], "9.9 5.5 4.6": ["outrage"], "7.1 7.1 3.4": ["corridor"], "7.3 5.7 3.1": ["watches"], "4.0 0.6 8.3": ["listings"], "8.7 4.3 3.4": ["fraction"], "7.8 16.7 8.0": ["smartphone"], "3.6 1.6 11.3": ["depressed", "bikeathon"], "10.5 10.8 6.1": ["realizing"], "11.9 5.6 2.9": ["sexy"], "9.4 10.4 6.6": ["addiction"], "12.9 3.5 4.5": ["creator"], "16.1 13.1 9.7": ["clouds"], "3.1 -2.9 -4.3": ["starred"], "8.1 1.4 -2.2": ["voluntarily"], "-3.8 3.3 4.6": ["retention"], "0.2 6.9 12.6": ["jacket"], "-2.3 18.9 12.5": ["hurts"], "-0.4 2.5 0.3": ["treasurer"], "10.6 12.4 15.3": ["hurricanes"], "3.0 -3.6 -2.1": ["underwent"], "17.1 -0.1 25.1": ["pan"], "-3.5 6.2 11.7": ["vaccines"], "2.5 17.0 3.6": ["scenarios"], "1.2 9.9 16.7": ["gardens"], "5.0 8.1 3.1": ["solved"], "4.4 1.0 3.7": ["stimulate"], "-2.2 9.0 -1.9": ["misconduct"], "19.2 8.8 0.7": ["leap"], "10.7 5.1 8.7": ["shelves"], "-9.5 10.7 4.1": ["candidacy"], "13.2 5.8 13.3": ["appetite"], "0.3 7.3 2.4": ["bothered"], "20.6 14.9 28.7": ["shell"], "8.7 1.1 -1.3": ["injection"], "7.4 21.3 10.4": ["essence"], "-6.9 -8.9 5.8": ["eligibility"], "18.7 9.8 16.2": ["sliding"], "7.9 4.2 2.1": ["pen"], "12.9 -2.3 3.3": ["bans"], "9.0 2.3 -0.9": ["automation"], "7.7 5.3 4.6": ["borrowed"], "10.4 5.1 -0.2": ["verge"], "3.5 9.3 36.2": ["poultry"], "11.6 13.1 7.9": ["promptly"], "11.0 11.3 1.6": ["sensors"], "16.2 16.8 5.2": ["worlds"], "1.7 13.6 -2.7": ["expose"], "8.5 17.4 6.1": ["accurately"], "2.7 -5.4 -3.0": ["structured"], "9.4 3.4 9.8": ["setup"], "-2.7 11.4 3.2": ["suffers"], "0.0 2.2 1.8": ["relied"], "-3.7 4.2 6.4": ["reunion"], "10.3 4.2 -2.1": ["marched"], "5.1 1.6 15.8": ["tags"], "8.3 5.8 17.3": ["tonne"], "5.2 12.0 0.2": ["shower"], "2.4 2.4 11.3": ["shirts"], "7.8 15.2 -0.7": ["continuously"], "8.8 7.1 5.6": ["similarly"], "8.3 17.6 20.5": ["batter"], "17.6 14.7 2.2": ["positioning"], "10.2 2.0 3.3": ["personalized"], "18.6 15.5 -1.6": ["towers"], "21.4 4.2 15.5": ["supermarket"], "11.4 13.2 0.9": ["notorious"], "3.9 15.4 10.0": ["happiness"], "3.2 3.6 3.3": ["filmed"], "41.2 23.8 25.9": ["monster"], "17.8 15.6 9.5": ["mysterious"], "6.2 3.6 5.1": ["kilometer"], "-2.0 4.4 4.0": ["specified"], "7.6 3.7 0.2": ["logical"], "-6.0 14.0 3.7": ["fiction"], "-1.8 17.5 8.0": ["isolation"], "3.3 5.2 4.3": ["indexes"], "7.7 2.8 7.0": ["vintage"], "-2.8 9.2 1.4": ["acute"], "-0.1 7.5 -0.3": ["reminds"], "11.9 6.5 6.0": ["glimpse"], "6.2 2.4 8.2": ["berth"], "4.5 -1.0 7.5": ["yielded"], "-0.1 -0.6 8.5": ["grams"], "-0.3 8.8 -1.0": ["subjected"], "17.8 35.5 22.0": ["pirates"], "6.6 5.4 6.9": ["streams"], "9.5 -1.8 3.4": ["notices"], "5.5 8.2 12.6": ["framing"], "8.0 5.2 3.2": ["clues"], "4.0 16.0 9.8": ["firefighter"], "5.3 13.4 3.0": ["ward"], "5.6 3.1 3.2": ["liter"], "14.2 6.3 4.9": ["decorated"], "4.0 9.0 2.0": ["embarrassed"], "7.7 2.6 0.6": ["helm"], "0.2 0.5 9.6": ["tightening"], "12.9 8.8 3.4": ["collectively"], "6.1 17.2 4.1": ["cheering"], "9.2 4.6 4.1": ["fascinating"], "13.2 7.5 1.7": ["sided"], "17.4 6.8 15.5": ["mice"], "0.9 7.3 3.7": ["technically"], "-1.1 8.1 5.2": ["reasonably"], "2.2 8.6 -1.6": ["notification"], "4.4 -0.1 -0.8": ["replaces"], "4.2 9.0 3.3": ["surprises"], "8.4 3.4 0.5": ["collided"], "14.9 1.7 5.7": ["lining"], "-2.1 -0.1 3.0": ["archive"], "1.0 8.2 2.9": ["coordinate"], "10.7 9.5 11.5": ["shattered"], "-4.1 0.2 12.3": ["bandwidth"], "20.6 15.8 13.3": ["mouse"], "-6.2 11.7 4.4": ["constituency"], "3.8 -3.2 -4.3": ["welcomes"], "13.3 5.9 3.4": ["ditch"], "14.3 15.2 9.4": ["practically"], "-1.5 15.0 11.1": ["outdoors"], "1.6 20.0 6.0": ["shouted"], "3.9 8.8 4.3": ["restoring"], "10.0 7.2 6.1": ["stabbing"], "6.2 7.1 9.5": ["positively"], "2.4 3.6 1.4": ["clause"], "-9.9 1.7 7.9": ["discretion"], "6.4 39.7 -0.1": ["extremists"], "5.3 21.9 10.2": ["drills"], "-2.1 14.2 1.4": ["abusive"], "0.6 11.9 3.7": ["sympathy"], "22.9 2.0 6.0": ["ailing"], "6.1 11.8 1.7": ["unified"], "8.9 6.4 2.0": ["grandson"], "5.3 3.4 -2.7": ["welcoming"], "3.5 3.4 0.2": ["newer"], "-3.3 8.1 -0.1": ["arise"], "8.5 -7.7 -1.5": ["comprising"], "-3.5 -0.7 7.4": ["portfolios"], "3.3 16.0 7.4": ["territories"], "2.3 3.7 42.6": ["pork"], "9.8 2.7 4.3": ["notch"], "1.1 6.6 5.3": ["misses"], "14.5 12.4 19.7": ["sink"], "10.0 12.8 10.2": ["throat"], "-2.5 15.3 -1.0": ["allegation"], "15.0 1.2 0.3": ["commercials"], "1.1 12.5 15.8": ["reactor"], "4.0 10.3 2.2": ["punched"], "1.5 8.3 -7.2": ["abducted"], "8.7 4.7 12.5": ["retirees"], "8.8 4.0 9.3": ["frames"], "10.3 5.2 1.6": ["admitting"], "-0.6 3.1 6.8": ["demolition"], "-1.4 -2.4 -1.8": ["requesting"], "12.9 1.5 6.1": ["hooked"], "5.6 4.7 2.9": ["attributable"], "29.7 0.1 8.2": ["themed"], "9.3 11.8 5.1": ["disrupt"], "-1.3 9.5 8.7": ["laughs"], "2.2 4.2 5.8": ["dean"], "-1.2 15.3 5.6": ["governmental"], "-2.1 14.1 3.9": ["judiciary"], "13.8 8.4 7.3": ["horizon"], "4.0 16.3 28.1": ["hunters"], "5.0 12.1 6.0": ["portrait"], "2.7 2.8 11.6": ["makeup"], "0.7 2.4 0.9": ["emphasize"], "3.4 -0.7 6.1": ["landfill"], "4.1 10.3 -1.7": ["utilizing"], "1.5 16.5 2.5": ["arc"], "26.3 3.9 5.9": ["surging"], "-1.0 2.8 3.3": ["newsletter"], "1.7 6.9 4.9": ["clinch"], "0.0 6.8 4.7": ["poetry"], "14.0 10.9 43.0": ["egg"], "24.0 13.9 11.2": ["vertical"], "6.0 13.2 4.5": ["ignoring"], "0.5 24.9 6.6": ["weaknesses"], "15.8 6.5 -3.6": ["supplying"], "17.4 16.7 7.5": ["accidentally"], "14.3 12.7 13.5": ["exporters"], "16.1 5.5 8.0": ["midday"], "13.4 6.2 2.3": ["miracle"], "-4.0 11.6 1.8": ["qualifier"], "7.4 16.0 8.5": ["suppose"], "9.9 -0.8 0.1": ["leasing"], "1.4 0.7 4.6": ["mandated"], "6.6 3.7 10.2": ["cracked"], "3.2 8.3 -1.4": ["portrayed"], "3.6 10.5 3.4": ["bogey"], "4.0 -9.6 0.6": ["certificates"], "8.6 5.8 6.7": ["compensate"], "-5.1 -4.1 15.5": ["slots"], "-4.5 6.3 15.0": ["heroin"], "9.3 7.4 8.8": ["bargain"], "7.3 2.5 26.3": ["plates"], "-0.2 10.0 23.7": ["sailing"], "-1.5 13.7 2.4": ["dispatched"], "-1.8 17.1 2.9": ["defensively"], "16.1 5.5 4.7": ["experimental"], "13.1 12.7 6.7": ["boring"], "5.3 2.5 10.4": ["staging"], "13.5 11.3 12.7": ["statue"], "7.1 31.5 1.5": ["propaganda"], "3.5 8.9 -0.5": ["consolidate"], "5.7 24.4 5.2": ["diplomacy"], "6.1 12.0 4.4": ["farther"], "1.9 -4.2 8.5": ["supplement"], "7.2 11.7 -1.3": ["capturing"], "3.5 4.5 3.8": ["standoff"], "5.5 6.7 4.6": ["rejection"], "-0.0 11.3 13.6": ["priests"], "11.0 1.0 -6.0": ["innovations"], "-1.4 8.9 3.2": ["lengths"], "-6.8 8.5 5.1": ["attributes"], "-1.8 16.7 -3.1": ["observation"], "-0.3 10.6 9.9": ["participant"], "-6.8 5.8 -3.7": ["contributors"], "-0.6 6.7 -1.1": ["rewarding"], "13.3 10.5 4.8": ["clever"], "-2.5 1.5 10.8": ["bikes"], "6.0 13.3 11.2": ["prolonged"], "10.1 4.9 9.9": ["treats"], "0.9 1.9 1.2": ["selecting"], "7.5 2.1 3.6": ["leisure"], "5.6 9.7 -2.6": ["burns"], "0.8 4.0 2.3": ["clarity"], "3.1 4.4 8.0": ["exceeding"], "1.0 1.5 4.4": ["professors"], "-0.4 13.2 5.2": ["wished"], "2.9 10.6 21.7": ["fruits"], "8.1 12.0 5.4": ["weakening"], "9.6 8.2 0.3": ["profound"], "4.2 1.3 4.8": ["inauguration"], "12.3 16.0 6.5": ["stranger"], "2.5 -6.4 0.2": ["smoothly"], "3.0 5.7 -2.2": ["slain"], "-4.1 5.6 4.9": ["specifics"], "26.9 8.1 6.5": ["akin"], "9.7 2.1 2.5": ["contentious"], "7.8 8.8 17.7": ["freezing"], "-8.0 11.5 15.6": ["caucus"], "0.4 7.1 0.9": ["contends"], "-3.6 12.6 -0.9": ["exchanged"], "0.3 -0.8 -2.6": ["premature"], "7.2 3.7 13.7": ["sidewalk"], "6.6 8.6 24.2": ["greens"], "3.5 9.1 1.7": ["rout"], "14.0 13.3 6.0": ["unexpectedly"], "15.2 13.2 22.9": ["bow"], "-0.9 0.3 -5.3": ["downloaded"], "6.3 17.1 -1.2": ["harmful"], "-1.0 35.3 0.3": ["militia"], "3.2 0.5 11.1": ["pinch"], "7.4 19.4 2.9": ["homeland"], "18.9 9.1 14.1": ["fancy"], "6.8 -1.6 8.3": ["ranged"], "-4.5 8.6 15.3": ["uninsured"], "-4.7 18.8 10.0": ["scrimmage"], "2.1 10.2 4.7": ["individually"], "12.6 8.3 20.7": ["clay"], "11.8 9.1 2.9": ["accord"], "-4.1 9.9 6.3": ["deceased"], "17.4 13.0 3.9": ["disastrous"], "-0.8 4.6 4.3": ["redevelopment"], "7.6 4.2 3.9": ["protections"], "3.7 10.9 -0.8": ["unconstitutional"], "-0.7 -0.4 4.1": ["termination"], "6.2 5.0 5.3": ["seating"], "11.4 11.1 10.7": ["disappear"], "6.0 14.8 5.9": ["undoubtedly"], "8.8 1.9 1.4": ["twins"], "2.9 15.7 1.7": ["uprising"], "-4.6 9.4 0.1": ["autopsy"], "2.9 12.1 13.3": ["thumb"], "11.6 12.2 -2.3": ["installations"], "6.9 10.5 7.8": ["stretches"], "8.7 12.1 7.3": ["drain"], "5.1 14.1 3.4": ["nickname"], "-5.4 2.6 1.5": ["caliber"], "0.9 6.8 3.7": ["minorities"], "20.9 16.0 10.6": ["endless"], "5.6 6.9 3.5": ["comparing"], "11.4 24.3 19.8": ["em"], "-2.9 3.8 1.0": ["outfielder"], "8.7 11.9 5.1": ["subtle"], "13.3 11.8 14.1": ["companion"], "12.1 6.6 6.9": ["broadcaster"], "4.6 0.6 7.6": ["density"], "7.4 4.3 1.8": ["fraudulent"], "9.7 -1.4 6.0": ["exhibits"], "15.9 3.1 8.5": ["biotechnology"], "7.0 6.6 2.0": ["adequately"], "10.0 0.7 8.0": ["batch"], "2.8 4.3 7.9": ["nightclub"], "-0.4 13.9 7.9": ["afterwards"], "9.4 6.0 5.6": ["fluid"], "24.2 4.2 7.4": ["famed"], "5.5 9.2 6.8": ["contamination"], "13.4 -0.3 1.7": ["pumps"], "-0.7 -0.6 1.4": ["scheduling"], "1.6 4.7 25.1": ["cooked"], "10.0 6.6 11.4": ["feeds"], "-4.6 9.4 1.9": ["disciplined"], "18.1 -2.2 -3.4": ["suing"], "25.0 3.2 7.2": ["slumped"], "2.8 3.7 -3.4": ["raided"], "10.6 9.4 6.8": ["indigenous"], "7.6 10.7 3.6": ["dug"], "12.3 6.1 -1.7": ["distributing"], "17.1 -0.7 4.0": ["popped"], "-0.4 6.3 9.3": ["grandparents"], "-8.6 11.5 14.6": ["primaries"], "23.9 1.8 1.8": ["spun"], "15.8 4.4 9.2": ["lifts"], "1.4 17.6 8.3": ["sequel"], "1.1 -2.6 6.2": ["arrange"], "2.2 8.3 4.8": ["economically"], "4.8 6.2 -4.0": ["honoring"], "3.6 5.9 9.5": ["dial"], "-1.6 12.8 1.9": ["defeats"], "5.0 3.0 11.2": ["artwork"], "-0.8 7.5 24.7": ["growers"], "7.0 1.4 10.1": ["leather"], "10.2 -2.7 1.0": ["modeling"], "13.0 4.7 10.4": ["shaky"], "1.0 11.7 12.3": ["illnesses"], "-5.3 1.5 4.7": ["singers"], "14.6 -0.7 -3.6": ["pictured"], "-0.2 11.9 2.1": ["personalities"], "8.0 -0.7 8.2": ["staffers"], "3.7 13.9 8.2": ["rubble"], "2.8 9.6 -6.6": ["inspiring"], "1.4 9.2 2.4": ["neglect"], "12.0 3.4 5.3": ["hype"], "4.2 5.0 2.0": ["trace"], "-2.6 25.1 10.1": ["bullets"], "6.0 3.1 12.7": ["pairs"], "-1.8 6.3 11.3": ["preceded"], "-0.8 19.7 0.8": ["necessity"], "3.0 6.2 11.1": ["unusually"], "-0.0 2.1 3.0": ["formats"], "22.1 6.8 4.7": ["crashing"], "5.4 12.4 24.1": ["dive"], "5.8 5.4 6.7": ["demographic"], "-1.7 -1.1 -1.9": ["exams"], "7.1 4.5 9.3": ["pools"], "0.8 14.3 8.5": ["guilt"], "1.9 3.7 6.0": ["contracting"], "6.7 4.1 2.8": ["void"], "27.3 6.1 17.7": ["float"], "4.5 -1.0 1.4": ["rented"], "6.6 5.2 16.5": ["opera"], "-0.9 6.4 4.7": ["asthma"], "-0.7 12.5 -0.2": ["intellectual"], "8.4 4.9 13.3": ["layers"], "15.0 11.3 6.5": ["ambitions"], "2.8 4.6 1.0": ["reliever"], "2.0 10.2 8.9": ["downside"], "-1.3 6.4 -0.7": ["acknowledges"], "11.7 0.0 5.5": ["loads"], "7.9 3.2 3.3": ["surpassed"], "13.3 -3.6 -7.4": ["marketed"], "9.0 10.6 13.9": ["hammer"], "9.6 13.1 2.7": ["gesture"], "12.0 9.1 7.3": ["ladder"], "13.8 6.3 12.7": ["bits"], "-5.5 13.5 1.1": ["negotiation"], "9.8 5.8 4.0": ["broadly"], "1.0 8.7 5.3": ["mechanisms"], "6.1 6.6 7.3": ["mineral"], "-1.1 16.5 10.0": ["grief"], "31.1 -4.2 11.9": ["hefty"], "18.1 19.8 7.1": ["masses"], "0.9 13.7 2.7": ["arson"], "7.6 5.3 6.2": ["touches"], "1.8 7.1 7.8": ["aspirations"], "0.0 4.6 8.1": ["orchestra", "inings"], "1.9 9.2 18.0": ["temple"], "1.6 1.9 -5.3": ["alleges"], "24.6 10.4 22.1": ["slice"], "-3.6 11.0 1.9": ["bye"], "-1.1 5.0 2.7": ["specify"], "9.0 8.0 -1.4": ["converting"], "14.4 4.9 3.7": ["phenomenal"], "-1.7 7.9 9.2": ["totals"], "5.8 9.5 7.2": ["forecasting"], "8.9 7.0 9.1": ["corresponding"], "9.3 3.9 15.3": ["cholesterol"], "17.2 12.6 4.1": ["sheer"], "2.1 -1.4 -1.9": ["arbitration"], "-5.9 6.0 0.6": ["contested"], "8.1 4.2 -4.9": ["stormed"], "7.7 11.4 6.3": ["hence"], "19.3 2.7 3.4": ["fortunes"], "4.2 4.6 7.8": ["outings"], "2.5 7.4 11.7": ["freight"], "2.5 0.4 2.2": ["inclusive"], "18.5 7.3 15.0": ["junk"], "11.6 10.7 7.1": ["leaning"], "9.9 5.8 10.4": ["warming"], "0.0 21.4 24.7": ["sailors"], "2.2 16.7 4.7": ["assumption"], "7.2 -1.2 3.9": ["heightened"], "6.8 7.5 5.9": ["authentic"], "-4.5 11.8 4.8": ["photographers"], "12.3 13.0 5.5": ["tricky"], "-1.1 11.8 12.5": ["taxi"], "9.9 9.2 3.2": ["keyboard"], "12.9 4.0 8.4": ["packing"], "12.5 23.3 16.8": ["flies"], "-4.7 -0.0 8.1": ["unsure"], "-1.0 8.6 10.2": ["stats"], "7.0 8.7 9.2": ["sprint"], "10.7 5.7 0.3": ["brink"], "0.9 8.2 4.3": ["ranges"], "0.5 -5.5 -0.1": ["chaired"], "8.6 8.9 5.8": ["railroad", "siding"], "7.7 17.9 4.1": ["precision"], "11.4 11.0 10.8": ["delight"], "-4.6 7.1 5.0": ["congregation"], "14.3 2.4 6.1": ["distinctive"], "17.4 6.8 10.5": ["jumps"], "11.5 -2.7 -1.1": ["highlighting"], "10.4 7.4 17.1": ["bull"], "10.7 6.8 8.8": ["stretching"], "2.3 5.1 2.9": ["tunes"], "0.1 16.4 4.7": ["patrols"], "-1.5 8.4 2.9": ["trainers"], "-4.8 9.4 -1.5": ["prosecuted"], "7.5 1.2 16.0": ["logging"], "16.2 7.3 7.0": ["grabbing"], "17.6 12.4 7.7": ["infamous"], "10.6 12.0 -0.3": ["unauthorized"], "8.6 0.4 7.0": ["cushion"], "7.4 23.5 10.8": ["gamers"], "10.8 0.2 3.3": ["protesting"], "3.1 12.7 14.9": ["tumor"], "-5.4 15.0 -0.5": ["exile"], "-3.1 6.5 9.8": ["preservation"], "3.1 5.8 7.2": ["poorest"], "1.0 4.0 -0.0": ["charitable"], "9.7 5.8 1.8": ["improper"], "-2.2 9.2 12.5": ["rains"], "9.0 8.6 2.2": ["riot"], "3.0 20.7 5.2": ["intentionally"], "-2.1 -3.6 -2.1": ["screened"], "4.2 6.1 4.1": ["configuration"], "5.7 2.7 0.9": ["prohibit"], "-5.0 6.3 6.5": ["quantity"], "10.1 5.3 5.5": ["experiments"], "10.3 29.3 15.6": ["trap"], "-8.5 0.7 0.7": ["unavailable"], "-2.5 11.2 -2.4": ["lied"], "2.0 8.0 2.0": ["woke"], "2.5 17.3 2.2": ["punish"], "-5.7 0.7 5.9": ["balances"], "-1.6 9.6 -1.9": ["utilized"], "-1.7 14.0 -1.0": ["criticize"], "10.6 7.8 6.4": ["furious"], "8.7 12.6 32.1": ["harbor"], "4.4 1.6 -1.4": ["hinted"], "10.6 10.3 9.6": ["playground"], "-4.1 0.2 0.9": ["qualification"], "6.3 12.9 4.8": ["confined"], "6.6 9.7 5.6": ["wonders"], "14.5 17.5 12.5": ["mask"], "9.3 -0.5 8.2": ["gig", "nonpetroleum"], "15.4 -5.8 -2.1": ["sponsoring"], "-6.2 14.0 -9.8": ["oath"], "1.0 1.3 3.9": ["renewable"], "5.5 9.4 14.3": ["rap"], "3.3 2.9 4.5": ["phases"], "5.1 13.6 7.5": ["digging"], "8.3 12.8 0.4": ["ambition"], "16.2 15.2 6.8": ["losers"], "17.3 13.4 14.3": ["shrinking"], "1.3 19.9 2.2": ["shouting"], "4.4 1.8 3.3": ["reversal"], "13.6 -3.6 4.0": ["billed"], "-0.3 21.8 5.8": ["consequence"], "2.0 5.0 2.9": ["pinned"], "13.2 5.0 6.9": ["pulls"], "-0.7 8.4 2.0": ["preserving"], "4.8 3.0 1.9": ["proposes"], "6.1 8.7 4.2": ["installment"], "13.8 5.4 13.1": ["blanket"], "0.8 4.5 4.8": ["pointer"], "-5.5 6.9 0.7": ["designation"], "-4.2 8.7 11.4": ["exhausted"], "10.7 6.9 -0.3": ["posing"], "8.1 22.0 13.0": ["mentality"], "13.3 1.1 8.3": ["federation"], "1.0 18.6 7.4": ["accordingly"], "-0.1 -2.3 -0.6": ["rigorous"], "2.8 10.4 -0.1": ["identities"], "11.2 10.2 8.3": ["hint"], "-7.7 -0.6 2.7": ["selections"], "-0.3 6.6 1.7": ["assessing"], "17.8 1.7 9.0": ["upward"], "1.9 10.6 8.8": ["baseline"], "10.0 2.7 19.4": ["pond"], "14.5 4.2 2.0": ["patented"], "11.8 1.7 0.5": ["expands"], "-2.6 -1.7 -3.8": ["verification"], "-2.3 -1.0 0.1": ["academics"], "5.9 2.2 2.5": ["campuses"], "3.0 11.5 -4.3": ["foremost"], "-2.9 8.7 2.7": ["handsets"], "4.0 5.3 1.8": ["plight"], "-3.2 18.3 5.9": ["heal"], "14.2 16.5 6.9": ["thieves"], "20.8 6.6 18.0": ["queen"], "6.6 10.9 4.0": ["solidarity"], "11.1 9.0 0.2": ["aided"], "0.4 4.5 1.1": ["overlooked"], "-7.6 8.6 -1.4": ["tolerated"], "7.7 3.5 17.7": ["coat"], "4.8 7.9 19.3": ["fertilizer"], "0.8 0.2 1.7": ["granting"], "-0.3 0.2 -5.8": ["trustee"], "5.8 6.6 2.8": ["planners"], "3.5 15.8 3.2": ["evacuate"], "4.6 13.5 0.3": ["inaccurate"], "9.0 6.8 5.6": ["columns"], "19.0 -2.5 -4.5": ["advertisements"], "-12.1 15.5 15.9": ["firearm"], "-5.0 8.7 5.3": ["golfers"], "3.9 6.7 9.7": ["driveway"], "12.8 18.8 5.2": ["lightning"], "4.5 1.7 7.8": ["altered"], "-1.6 11.0 5.3": ["standpoint"], "6.1 -3.0 10.5": ["tighter"], "13.2 -3.6 6.6": ["subsidy"], "6.0 13.5 3.1": ["indirectly"], "20.7 3.0 9.0": ["richest"], "2.5 5.5 10.2": ["sunny"], "9.0 11.4 2.6": ["absorb"], "9.0 2.9 6.3": ["guides"], "9.3 8.5 13.5": ["astronauts"], "2.7 16.4 3.5": ["weaken"], "6.4 7.5 -0.3": ["opposes"], "11.0 10.8 5.0": ["evolving"], "-7.5 -1.3 5.2": ["jeans"], "4.8 0.1 10.2": ["festivities"], "12.2 -2.8 -5.6": ["touted"], "19.6 14.1 10.4": ["lobbyists"], "4.6 6.7 6.8": ["beta"], "10.7 8.6 1.7": ["toilet"], "13.8 2.2 18.1": ["grocery"], "9.8 19.4 5.9": ["policeman"], "3.1 8.1 1.2": ["plaintiff"], "0.8 -3.1 15.0": ["luncheon"], "-8.0 13.0 2.8": ["listeners"], "-2.8 -0.8 17.1": ["kg"], "3.4 3.5 12.3": ["costumes"], "6.7 8.0 5.7": ["flawed"], "7.7 8.9 8.7": ["builder"], "10.6 1.8 0.5": ["pledges"], "15.6 7.8 -1.6": ["outskirts"], "2.4 0.4 11.9": ["closures"], "8.1 2.4 4.2": ["businessmen"], "3.9 3.9 4.7": ["module", "watts"], "16.9 -2.0 8.9": ["royalty"], "4.5 10.4 -4.4": ["criticizing"], "12.1 1.9 11.7": ["nicely"], "3.5 18.5 11.9": ["tendency"], "1.4 10.5 8.5": ["certainty"], "11.6 -7.8 -8.4": ["partnered"], "4.4 3.7 2.9": ["wheelchair"], "10.6 27.7 4.4": ["obstacle"], "8.3 0.5 9.7": ["sheets"], "-2.7 9.7 -4.1": ["proactive"], "-1.4 3.5 -0.4": ["coroner"], "5.4 3.8 3.0": ["shaping"], "1.8 11.9 3.9": ["smiles"], "8.7 10.6 7.5": ["foundations"], "5.2 -2.0 11.6": ["festivals"], "4.1 11.9 5.3": ["cabin"], "5.8 10.1 17.4": ["smokers"], "4.7 12.3 -2.5": ["protects"], "6.5 5.8 1.7": ["exclude"], "23.0 -3.4 14.9": ["stuffed"], "13.1 -0.7 4.7": ["doubling"], "2.2 6.3 1.9": ["showers"], "8.1 1.3 7.7": ["rupees"], "12.2 10.8 6.5": ["purely"], "2.6 3.7 6.2": ["cares"], "19.9 -0.0 12.6": ["topping"], "11.8 16.8 6.1": ["catastrophic"], "-0.5 0.1 18.8": ["breast"], "12.4 8.2 0.4": ["shutting"], "-6.7 12.2 11.1": ["chemotherapy"], "-2.2 11.7 6.6": ["tolerance"], "3.0 15.5 9.8": ["bullying"], "-5.2 16.2 4.5": ["wives"], "8.7 5.9 6.2": ["fallout"], "-2.6 1.4 -2.4": ["tapes"], "10.7 8.5 11.1": ["ballpark"], "3.9 10.6 15.9": ["gloves"], "4.1 12.8 16.6": ["whites"], "1.7 -3.6 3.4": ["benefiting"], "11.7 5.4 5.3": ["southeastern"], "8.2 6.8 -3.3": ["upgrading"], "3.7 -2.3 3.5": ["earns"], "14.6 18.8 14.3": ["piracy"], "16.2 7.2 17.0": ["animation"], "6.2 20.7 4.7": ["attacker"], "6.4 4.3 -0.5": ["emergence"], "5.9 6.2 0.2": ["precedent"], "-0.3 13.9 1.5": ["organizational"], "4.4 5.0 0.0": ["literacy"], "9.0 6.3 7.7": ["basics"], "14.7 18.7 7.2": ["presumably"], "9.0 3.0 7.3": ["northeastern"], "0.3 17.4 6.9": ["aces"], "13.9 6.4 3.2": ["enthusiasts"], "10.2 -2.1 1.4": ["generates"], "12.8 2.2 4.0": ["coveted"], "14.9 21.8 9.3": ["lover"], "-1.8 -1.1 -1.1": ["clarify"], "9.6 1.4 7.6": ["elegant"], "-4.1 5.9 4.3": ["concussion"], "6.3 5.3 15.3": ["jam"], "-0.8 8.4 4.1": ["wears"], "7.2 2.2 5.6": ["disrupted"], "16.3 8.9 15.2": ["dumping"], "14.3 12.3 -2.8": ["nearest"], "10.5 7.5 12.6": ["shipment"], "5.0 17.6 6.9": ["vulnerability"], "3.0 22.9 10.0": ["liberty"], "10.4 18.1 7.9": ["disasters"], "-5.1 11.3 1.7": ["accomplishment"], "0.9 8.1 1.7": ["comparisons"], "8.8 -1.5 -3.2": ["advising"], "7.2 4.3 2.6": ["downloads"], "28.0 10.5 9.8": ["spinning"], "6.0 5.8 5.3": ["tenth"], "5.6 14.2 5.9": ["envoy"], "-3.4 12.3 5.4": ["offensively"], "5.0 13.8 5.3": ["crises"], "1.0 3.9 3.1": ["fairness"], "1.4 -6.5 1.4": ["cancellation"], "5.6 17.4 0.5": ["perimeter"], "10.9 9.3 0.3": ["filter"], "-1.1 1.4 -1.3": ["acquitted"], "2.4 8.2 5.4": ["boarding"], "-1.0 9.8 5.5": ["inconsistent"], "2.0 13.3 12.7": ["boundary"], "-1.9 10.9 2.4": ["surgical"], "-3.5 5.8 6.0": ["constraints", "rewatched"], "0.8 24.1 9.9": ["troop"], "12.0 11.5 3.6": ["navigate"], "29.8 15.5 16.4": ["robot"], "-8.4 1.3 2.6": ["scholars"], "15.2 6.0 -3.7": ["footprint"], "8.1 16.2 0.3": ["resistant"], "0.5 11.2 5.2": ["possess"], "9.6 4.1 3.3": ["youngster"], "7.4 -2.2 -10.1": ["partnering"], "9.9 9.9 9.0": ["attractions"], "0.7 9.9 -1.7": ["reactions"], "12.7 15.6 5.6": ["swift"], "-2.5 -3.6 5.6": ["backlog"], "14.7 8.7 6.5": ["franchises"], "16.1 7.4 2.8": ["cheered"], "-8.9 4.1 -3.6": ["prescribed"], "12.0 0.9 11.4": ["fabulous"], "0.5 11.1 18.3": ["homeowner"], "0.1 7.9 2.9": ["innocence"], "8.2 28.4 9.7": ["darkness"], "8.8 15.2 2.0": ["imagined"], "1.8 27.3 8.2": ["terrain"], "13.8 1.6 -2.6": ["tore"], "3.5 0.6 2.9": ["modules"], "1.2 6.0 6.5": ["fumble"], "-7.4 12.8 1.8": ["strive"], "3.4 3.6 6.4": ["proceeding"], "14.6 6.1 7.3": ["dismal"], "0.3 45.8 6.1": ["insurgent"], "-5.1 0.0 2.5": ["cared"], "6.5 10.0 7.4": ["grasp"], "18.4 7.3 2.6": ["tablet"], "2.9 11.7 11.3": ["mold"], "4.1 2.9 6.6": ["submitting"], "2.8 1.6 3.2": ["justices"], "2.8 2.0 -1.7": ["arising"], "7.4 13.2 1.9": ["compounds"], "28.2 6.8 6.4": ["staggering"], "-2.8 16.9 4.6": ["narrative"], "6.3 7.8 29.6": ["delicious"], "-1.9 3.0 16.5": ["pills"], "5.7 8.1 4.4": ["spreads"], "1.8 4.8 19.4": ["liver"], "-10.0 9.9 3.0": ["scorers"], "-2.6 -3.5 3.9": ["productions"], "1.6 8.0 -3.6": ["leveled"], "-1.4 2.5 7.0": ["literary"], "6.7 -0.0 3.8": ["consist"], "1.4 9.7 5.1": ["insufficient"], "7.7 9.9 44.9": ["turkey"], "7.8 4.6 1.9": ["intriguing"], "8.2 2.0 17.5": ["pros"], "2.6 7.5 23.5": ["varieties"], "3.4 16.5 9.0": ["lightly"], "3.2 6.8 1.6": ["narrowly"], "15.6 10.2 5.5": ["scoreboard"], "8.5 8.6 17.1": ["costume"], "6.6 9.6 3.4": ["fatigue"], "7.9 16.3 6.5": ["awkward"], "0.8 9.9 11.9": ["adaptation"], "8.7 -1.4 62.7": ["salmon"], "11.2 11.8 6.7": ["outrageous"], "5.3 1.4 1.5": ["assurances"], "2.6 -0.1 6.8": ["tighten"], "4.1 2.7 2.7": ["finalist"], "-5.1 4.5 1.3": ["briefed"], "-4.0 11.9 27.5": ["breeding"], "-1.7 9.8 -3.8": ["assaulted"], "2.8 9.8 -1.8": ["accuse"], "13.0 6.5 2.2": ["marketers"], "4.7 9.3 20.2": ["shallow"], "7.3 12.8 6.8": ["prediction"], "12.8 3.8 13.4": ["bump"], "6.0 -4.0 3.2": ["reconsider"], "5.0 4.9 0.4": ["optimize"], "3.3 16.3 -4.1": ["tortured"], "-1.1 18.3 8.0": ["deliberate"], "17.8 8.4 13.1": ["cute"], "10.7 -3.8 2.3": ["lodged"], "5.0 7.3 8.5": ["doping"], "14.7 9.3 9.1": ["slipping"], "6.0 8.2 7.0": ["curve"], "4.9 14.6 -0.1": ["embarrassment"], "-5.2 -1.2 -1.0": ["renovations"], "3.8 2.9 7.6": ["grabs"], "4.1 8.5 5.1": ["assumes", "fibrillation"], "9.8 13.6 1.1": ["potent"], "6.6 10.0 7.1": ["pause"], "11.3 9.4 3.5": ["rage"], "4.6 4.7 -2.0": ["versatile"], "8.6 -2.2 -2.7": ["leased"], "-4.0 21.5 5.2": ["gunfire"], "1.2 6.9 2.5": ["inherited", "judgers"], "2.6 9.6 11.7": ["fluctuations"], "5.9 9.3 1.0": ["reorganization"], "9.7 10.5 24.1": ["sheep"], "6.7 26.5 2.7": ["unpopular"], "7.0 4.9 2.6": ["tangible"], "5.4 4.9 9.3": ["hats"], "3.5 -0.3 2.8": ["composition"], "1.3 5.7 0.2": ["forged"], "19.2 -2.3 2.2": ["rocked"], "3.7 0.8 11.5": ["shorts"], "2.0 5.6 3.6": ["homework"], "4.8 7.6 7.6": ["trafficking"], "9.7 -2.8 9.8": ["hikes"], "7.1 1.6 2.8": ["narrowed"], "15.2 -2.0 11.6": ["weighs"], "3.9 5.3 -4.8": ["entertain"], "0.9 -4.9 0.9": ["unpaid"], "-6.5 10.1 11.5": ["rainfall"], "6.1 2.4 7.8": ["optional"], "11.4 5.6 14.5": ["cookies"], "9.3 7.9 2.1": ["overwhelmingly"], "13.5 7.3 2.0": ["intensified"], "14.7 4.3 15.2": ["crafts"], "10.3 -2.8 -0.6": ["protested"], "7.0 2.8 7.4": ["ample"], "5.1 -0.0 6.1": ["clips"], "1.6 12.7 7.8": ["equality"], "-10.5 -0.8 -2.4": ["recordings"], "-0.2 2.3 -4.7": ["transferring"], "4.0 -0.8 -0.7": ["accepts"], "-3.7 37.8 6.8": ["tactical"], "15.2 -0.0 12.2": ["tube"], "8.7 11.5 5.0": ["widow"], "15.7 9.8 6.7": ["grim"], "-0.7 13.7 13.0": ["fastball", "patrollers"], "36.5 17.9 4.3": ["empire"], "-5.7 9.5 3.3": ["imprisonment"], "4.9 13.4 4.5": ["buttons"], "-3.7 3.7 1.3": ["ensured"], "-1.8 -4.2 2.8": ["debated"], "6.1 11.9 9.6": ["predictable"], "2.6 33.0 18.5": ["naval"], "10.8 4.9 3.1": ["fever"], "-5.6 5.6 7.9": ["divorced"], "8.6 6.9 9.3": ["flip"], "21.7 15.3 1.8": ["immense"], "9.2 1.9 8.1": ["steer"], "3.8 3.9 1.5": ["riots"], "4.9 8.7 1.6": ["confusing"], "12.6 3.8 5.3": ["consume"], "26.4 2.8 5.8": ["sprawling"], "-9.1 12.8 2.4": ["emotionally"], "-1.1 3.5 7.2": ["airing"], "-1.7 10.6 4.5": ["rematch"], "10.4 14.6 2.6": ["inherent"], "6.8 15.1 6.4": ["hills"], "4.6 1.3 63.1": ["seafood"], "1.9 32.3 10.9": ["aggression"], "16.6 12.7 3.6": ["umbrella"], "10.4 7.3 -0.5": ["undertaking"], "2.8 8.8 -0.6": ["ministries"], "-3.6 4.6 7.9": ["exceptions"], "-1.4 22.6 9.2": ["rifle"], "-1.8 13.5 5.4": ["al"], "7.8 1.6 0.2": ["reacted"], "-7.5 -2.6 5.7": ["admissions"], "14.4 3.5 6.3": ["spilled"], "3.8 7.8 6.4": ["nephew"], "8.1 5.5 7.2": ["optical"], "5.8 8.9 1.3": ["authorization"], "3.7 4.7 7.4": ["broadcasters"], "5.9 8.6 3.0": ["inspector"], "10.3 13.6 1.3": ["cooperating"], "-2.6 8.9 2.8": ["advisors"], "3.9 19.3 13.9": ["tribes"], "5.6 0.2 3.0": ["cleaner"], "8.1 6.1 10.1": ["impoverished"], "-2.5 9.9 -5.2": ["asserted"], "3.2 1.4 7.0": ["notched"], "4.5 3.8 -2.0": ["commercialization"], "14.1 6.2 -2.4": ["branding"], "1.1 10.8 1.1": ["golfer"], "9.7 -4.4 -0.2": ["recycled"], "4.6 17.4 11.6": ["gays"], "3.7 6.5 0.8": ["reigning"], "-0.2 6.1 4.0": ["accumulated"], "3.2 5.9 -0.4": ["troubling"], "5.2 -2.0 5.9": ["upscale"], "5.9 11.1 7.1": ["infield"], "8.2 6.9 13.5": ["cooler"], "5.9 -1.2 -2.5": ["owes"], "9.1 9.7 22.7": ["nuts"], "11.4 5.8 -0.5": ["thrilling"], "6.9 12.7 4.8": ["muscles"], "9.7 4.0 7.1": ["widening"], "1.9 -0.5 15.4": ["sampling"], "15.0 3.2 2.4": ["graphic"], "2.2 6.0 7.7": ["hampered"], "8.6 5.2 5.8": ["shaken"], "5.4 6.4 2.0": ["interfere"], "3.1 7.9 3.9": ["pleasant"], "8.2 1.1 4.5": ["busiest"], "6.6 5.1 7.4": ["clutch"], "1.6 2.0 2.2": ["forensic"], "12.8 1.4 0.0": ["waved"], "8.2 -6.8 -1.7": ["comprises"], "10.8 -1.6 -3.2": ["debuted"], "21.2 5.1 16.0": ["chunk"], "-2.1 13.5 3.5": ["undercover"], "11.5 1.6 2.0": ["downgraded"], "12.7 3.2 7.2": ["tents"], "-1.4 5.1 6.4": ["newcomers"], "-8.0 -0.1 -3.4": ["edited"], "3.1 8.0 6.1": ["instability"], "3.9 7.0 -1.5": ["presently"], "11.8 11.2 -4.8": ["integrating"], "1.0 8.3 1.6": ["fuels"], "20.9 5.5 7.4": ["swung"], "9.0 4.7 8.3": ["judging"], "-0.9 6.3 1.3": ["translated"], "11.0 7.7 21.9": ["surf"], "0.4 10.3 1.9": ["immunity"], "10.6 11.3 -0.4": ["eg"], "5.2 7.5 8.6": ["refineries"], "-2.2 15.3 0.6": ["prosecute"], "1.8 21.4 1.0": ["challenger"], "3.4 10.1 -0.8": ["thriller"], "-2.7 0.4 -4.2": ["amenities"], "4.0 28.8 1.7": ["casualty"], "6.4 14.7 3.7": ["refuge"], "-6.0 9.1 16.6": ["handgun"], "16.1 18.2 8.3": ["genius"], "3.3 11.1 11.5": ["pedestrian"], "6.8 10.0 9.1": ["succession"], "1.9 12.5 9.7": ["premise"], "0.5 -0.4 -1.3": ["volunteered"], "4.5 -4.0 -3.1": ["objected"], "-3.5 13.9 13.0": ["bowlers"], "10.9 15.6 -0.7": ["rumor"], "7.0 11.6 1.3": ["unsafe"], "-8.2 8.2 5.2": ["therapies"], "-4.1 -0.5 0.4": ["disagreed"], "11.1 5.0 7.4": ["dire"], "9.0 4.8 13.9": ["barn"], "-10.0 5.1 4.0": ["bowled"], "7.8 3.5 1.3": ["chambers"], "6.1 6.8 -0.4": ["flaws"], "-3.3 -2.5 1.6": ["mailed"], "2.1 1.1 9.9": ["preserved"], "11.2 5.5 11.7": ["outline"], "14.1 3.9 9.9": ["destined"], "8.0 9.8 2.3": ["blank"], "-0.8 10.5 3.7": ["applause"], "13.8 8.3 12.2": ["exotic"], "-0.1 20.1 -1.2": ["squads"], "-4.7 3.6 4.4": ["continuity"], "4.0 7.5 4.3": ["wishing"], "2.5 1.6 3.2": ["regained"], "12.0 -5.7 1.5": ["approves"], "10.8 0.7 1.8": ["savvy"], "14.9 5.3 7.3": ["packs"], "4.6 9.6 0.8": ["defining"], "11.6 2.5 4.6": ["fitted"], "5.4 9.9 14.0": ["migrants"], "-6.3 4.4 8.6": ["filmmakers"], "3.6 6.7 10.9": ["satisfying"], "11.3 -0.5 5.7": ["tentative"], "-2.0 6.5 -2.3": ["encouragement"], "-0.3 3.8 3.9": ["ejected", "rulemakings"], "2.5 4.0 11.5": ["wallet"], "-0.5 18.3 8.8": ["insider"], "3.5 7.1 3.3": ["amazed"], "-3.2 7.2 2.0": ["enjoyable"], "5.6 5.6 6.8": ["merits"], "1.8 9.9 11.9": ["cheating"], "2.3 7.4 8.0": ["beneficiaries"], "4.8 6.3 1.7": ["analytics", "decodes"], "8.5 3.8 -2.9": ["confirming"], "12.0 10.4 12.9": ["tanker"], "2.6 6.8 4.2": ["adapted"], "9.0 11.2 7.0": ["blaming"], "20.5 2.7 2.1": ["entrepreneur"], "2.8 -2.7 1.2": ["stringent"], "11.3 13.7 4.5": ["sensor"], "10.6 13.0 0.3": ["cease"], "-5.7 2.6 1.0": ["disciplinary"], "17.1 -3.2 -4.7": ["mln"], "-7.3 1.1 6.6": ["juniors"], "0.2 0.7 -2.2": ["toured"], "8.2 17.6 -1.5": ["horrific"], "0.6 5.7 4.7": ["interrupted"], "7.4 17.7 7.4": ["indirect"], "0.7 0.7 -0.3": ["choir"], "0.5 7.4 9.5": ["insured"], "22.8 4.7 11.3": ["heavyweight"], "16.8 26.8 7.9": ["shield"], "1.4 11.5 2.4": ["prevents"], "-2.0 9.8 11.1": ["burial"], "4.9 10.7 1.9": ["bounds"], "1.2 -9.0 4.4": ["seminars"], "7.2 6.5 6.9": ["indefinitely"], "1.0 3.3 6.3": ["registering"], "14.3 8.5 14.1": ["loading"], "19.2 15.1 10.2": ["magical"], "13.6 7.7 20.0": ["delicate"], "8.3 32.7 1.8": ["allied"], "-4.2 1.7 5.9": ["notebook"], "11.0 3.8 8.1": ["lingering"], "10.3 5.2 -1.0": ["engineered"], "6.8 12.4 -0.3": ["hurdle"], "4.1 6.0 22.0": ["skate"], "-10.4 -2.1 -2.4": ["qualifications"], "7.0 15.3 9.3": ["miserable"], "8.5 12.3 3.9": ["breathe"], "6.4 6.1 3.9": ["cracks"], "20.7 11.2 2.9": ["unnamed"], "5.9 14.6 12.8": ["bride"], "3.8 6.9 3.9": ["messaging"], "1.4 13.2 8.1": ["hurry"], "11.9 18.0 -0.2": ["deadliest"], "10.1 8.2 -0.4": ["comfortably"], "10.7 2.1 3.9": ["neat"], "-1.1 -2.7 -4.4": ["enhancements"], "-6.1 -1.1 5.4": ["principals"], "11.7 9.0 17.9": ["bucket"], "5.0 11.3 8.5": ["thrive"], "7.6 19.9 10.1": ["inevitably"], "12.1 7.5 9.1": ["ruined"], "4.5 -3.6 2.4": ["discounted"], "20.3 10.3 12.3": ["stiff"], "-2.6 14.3 2.9": ["verbal"], "5.5 25.1 12.6": ["liberals"], "-2.0 26.4 4.5": ["retaliation"], "16.1 10.6 10.2": ["shrink"], "4.8 0.9 6.4": ["commence"], "9.1 4.8 6.9": ["drastic"], "11.9 -7.2 4.9": ["spurred"], "13.6 8.0 4.3": ["pouring"], "18.0 9.5 0.7": ["merge"], "-5.6 -5.2 -3.7": ["garnered"], "5.4 8.9 4.2": ["whatsoever"], "4.5 21.9 11.2": ["theirs"], "5.5 5.1 4.0": ["angered"], "-0.9 5.6 5.7": ["councilor"], "3.5 9.2 18.8": ["tongue"], "0.6 1.7 12.1": ["autism"], "4.9 7.1 4.8": ["reign"], "1.1 10.6 -1.9": ["compromised"], "10.2 -8.9 1.5": ["tripled"], "2.5 10.4 3.1": ["surgeon"], "0.2 7.6 -2.9": ["efficiencies"], "6.1 4.9 2.1": ["analyzing"], "14.7 6.5 6.4": ["bidders"], "4.0 7.3 9.1": ["hectares"], "-0.2 31.8 4.1": ["hatred"], "17.2 5.9 8.4": ["prop"], "7.9 9.7 -3.8": ["accuses"], "3.0 10.5 3.0": ["solving"], "7.5 10.9 8.1": ["appropriately"], "11.1 2.4 7.7": ["tainted"], "32.5 -0.3 10.5": ["mega"], "21.5 4.4 11.0": ["slick"], "13.0 13.6 1.8": ["unwanted"], "3.2 15.1 2.3": ["tolerate"], "21.2 15.1 15.3": ["artificial"], "9.7 7.7 6.7": ["herein"], "6.0 4.2 21.4": ["cows"], "0.5 12.7 7.9": ["influences"], "9.9 15.4 -5.9": ["leaks"], "5.3 5.9 16.9": ["flavors"], "14.5 20.3 6.7": ["crush"], "6.9 1.5 1.3": ["binding"], "12.3 2.3 -0.9": ["lightweight"], "-3.8 7.4 5.3": ["enforced", "assenting"], "1.7 1.6 4.5": ["overview"], "3.3 5.0 -0.7": ["pressured"], "4.4 14.9 3.6": ["irresponsible"], "1.5 12.7 9.2": ["laughter"], "0.3 2.3 10.6": ["transplant"], "4.6 9.8 22.1": ["females"], "-2.4 4.4 8.8": ["continuation"], "6.1 8.7 4.0": ["thirty"], "5.8 -0.5 4.4": ["infants"], "6.3 3.0 4.9": ["slate"], "-1.5 14.6 3.1": ["fatalities"], "-3.4 1.0 -0.2": ["readings"], "4.1 -0.1 10.5": ["stems"], "10.8 12.7 6.2": ["societies"], "-2.1 4.3 -1.3": ["retaining"], "7.9 4.3 14.0": ["dunk"], "2.1 11.2 28.7": ["lakes"], "3.3 3.0 5.9": ["impress"], "1.5 18.0 12.4": ["kiss"], "2.4 11.0 8.1": ["aunt"], "-0.0 6.0 4.8": ["bracket"], "9.9 -3.5 0.4": ["donating"], "0.9 -3.8 3.0": ["terminated"], "4.3 13.8 7.9": ["classmates"], "3.0 8.5 5.3": ["dealership"], "17.8 11.9 11.6": ["magnificent"], "12.0 11.7 8.4": ["brains"], "7.6 12.7 9.6": ["charm"], "-0.1 2.0 7.9": ["cycles"], "13.6 19.5 8.0": ["catastrophe"], "1.6 -1.4 7.9": ["assistants"], "6.7 7.4 18.4": ["buck"], "8.6 11.9 11.7": ["truce"], "-7.4 13.5 -3.4": ["whereabouts"], "6.4 27.5 22.8": ["navy"], "6.3 17.8 9.4": ["epidemic"], "11.1 4.7 6.9": ["champ"], "-4.5 6.7 10.8": ["skiing"], "9.0 13.6 6.0": ["humble"], "-5.8 11.7 0.6": ["assignments"], "2.9 16.4 6.2": ["geographic"], "6.6 -0.8 9.1": ["openings"], "6.6 -1.0 9.1": ["architectural"], "6.3 -1.8 9.5": ["pronounced"], "10.0 12.3 3.7": ["physics"], "3.1 12.5 -8.6": ["answering"], "9.5 16.5 7.2": ["backward"], "3.0 3.8 13.5": ["variations"], "10.7 8.2 6.2": ["nonetheless"], "9.3 17.4 2.7": ["enduring"], "5.4 -4.5 1.8": ["persuaded"], "1.8 8.5 7.5": ["filmmaker"], "1.6 13.9 2.6": ["deter"], "-5.7 14.0 7.2": ["severity"], "6.2 0.2 -0.5": ["specifications"], "6.4 6.1 6.5": ["deteriorating"], "-1.7 18.1 4.6": ["checkpoint"], "3.3 5.9 1.9": ["psychology"], "-2.3 11.2 2.5": ["policing"], "4.6 -6.4 3.5": ["tailored"], "-0.1 -2.9 2.2": ["submissions"], "-0.8 21.1 9.4": ["spouse"], "-3.4 -1.8 9.6": ["reimbursement"], "-1.3 15.9 5.4": ["compassion"], "13.3 13.6 13.4": ["oh"], "-5.6 32.7 6.1": ["ideology"], "17.5 13.8 16.2": ["purple"], "21.6 21.4 4.9": ["formidable"], "-0.3 5.3 5.1": ["departed"], "5.3 17.8 0.1": ["deploying"], "2.7 16.4 6.4": ["conscience"], "-3.1 16.2 4.7": ["discharge"], "14.5 4.3 8.7": ["stack"], "12.5 10.6 7.4": ["heck"], "13.7 6.4 8.7": ["swings"], "-2.8 2.1 1.6": ["advises"], "4.1 -0.6 -3.5": ["connects"], "4.3 12.9 17.4": ["shotgun"], "2.1 7.5 14.0": ["bishops"], "6.4 30.1 10.7": ["tactic"], "-2.6 4.3 0.5": ["efficacy"], "7.4 9.6 5.5": ["dugout"], "-1.5 5.5 0.2": ["edit"], "11.1 10.6 24.3": ["dock"], "0.1 15.3 12.1": ["electorate"], "0.2 18.9 2.9": ["praying"], "5.9 0.0 6.8": ["taped"], "11.5 4.3 8.4": ["bang"], "2.0 10.5 5.9": ["nonsense"], "21.2 7.0 22.9": ["cow"], "-3.0 2.2 -1.9": ["amend"], "6.4 6.0 3.3": ["catalyst"], "8.8 10.4 7.3": ["pushes"], "2.5 5.2 2.8": ["timeline"], "15.7 9.8 9.1": ["cables"], "-0.3 4.4 7.0": ["ratios"], "8.5 7.6 25.4": ["flower"], "7.1 4.3 7.1": ["chorus"], "10.4 1.2 0.0": ["technicians"], "22.1 -2.8 -1.3": ["unveil"], "12.0 18.0 9.8": ["rescuers"], "-3.8 2.5 3.4": ["speculate"], "9.9 5.1 10.2": ["scrambling"], "16.5 9.4 -0.7": ["backers"], "7.8 2.6 3.3": ["privatization"], "5.3 13.0 4.4": ["cheers"], "9.8 -1.9 1.7": ["micro"], "17.0 3.5 26.6": ["butter"], "0.5 9.7 4.6": ["seated"], "17.1 25.6 12.5": ["proxy"], "11.9 4.2 5.4": ["speedy"], "-2.3 0.9 0.7": ["diverted"], "8.7 10.3 4.0": ["alarming"], "3.6 17.9 10.7": ["caller"], "4.9 10.5 3.2": ["wreckage"], "9.0 -2.9 1.2": ["approving"], "16.5 5.2 13.6": ["drum"], "8.3 3.6 0.8": ["definitive"], "17.0 6.4 -2.9": ["merged"], "15.6 13.6 8.5": ["projection"], "-5.2 13.5 7.8": ["batsman"], "2.3 0.2 6.8": ["contributes"], "-5.3 4.7 -0.8": ["competent"], "2.9 7.9 9.7": ["downhill"], "8.5 8.4 9.3": ["nerves"], "6.0 11.4 -2.6": ["massacre"], "1.4 15.5 3.7": ["contempt"], "6.4 7.0 1.7": ["ridden"], "-3.4 12.1 10.6": ["elder"], "-3.5 4.8 4.8": ["subdivision"], "7.7 12.0 5.0": ["orbit"], "8.3 17.1 -0.6": ["distraction"], "1.3 -3.9 1.0": ["receipts"], "9.3 17.3 7.4": ["tricks"], "18.8 21.2 5.6": ["relentless"], "14.1 4.8 1.5": ["demise"], "4.4 9.0 -0.0": ["incorrect"], "7.1 11.7 9.1": ["subway"], "4.1 1.2 8.5": ["platinum"], "-4.8 5.9 1.9": ["considerations"], "3.7 18.1 11.0": ["unpredictable"], "4.5 13.6 6.7": ["putt"], "4.5 8.0 10.5": ["commuters"], "6.8 10.4 1.1": ["resisted"], "15.7 6.1 -2.5": ["rumored"], "11.3 7.2 7.9": ["drums"], "4.5 4.6 11.8": ["comedian"], "6.0 7.6 7.7": ["biology"], "5.0 26.1 12.5": ["peoples"], "-1.3 0.7 -3.5": ["verified"], "5.5 14.1 17.9": ["ingredient"], "-2.3 -2.9 12.5": ["seasoned"], "5.9 3.2 5.8": ["disk"], "17.0 15.0 10.0": ["heaven"], "17.7 2.1 11.6": ["pad"], "8.3 13.5 8.3": ["clue"], "9.6 8.8 12.7": ["exterior"], "0.3 10.5 1.2": ["historian"], "8.5 -2.8 12.9": ["auctions"], "3.8 3.4 -1.4": ["summoned", "summated"], "3.2 5.3 8.3": ["brakes"], "-4.7 17.4 8.9": ["excuses"], "9.4 2.8 7.3": ["cracking"], "-4.2 18.8 2.0": ["imperative"], "-10.8 -0.2 7.0": ["occupancy"], "9.6 9.8 16.5": ["rope"], "9.9 7.4 4.9": ["seizure"], "1.8 1.1 9.9": ["inter"], "6.0 10.1 3.6": ["evolve"], "-7.9 2.1 14.4": ["lacrosse"], "2.8 12.5 3.4": ["cried"], "9.8 8.0 -0.2": ["denounced"], "2.6 10.1 3.8": ["negotiators"], "-1.3 5.7 -2.1": ["diagnostic"], "0.9 6.8 5.6": ["initiate"], "1.2 4.4 2.0": ["relates"], "3.6 11.1 7.9": ["adjusting"], "11.5 10.3 3.7": ["signaling"], "-1.8 -2.6 16.2": ["k"], "-1.9 3.2 11.2": ["resorts"], "8.1 3.1 10.3": ["rand"], "8.1 17.5 1.5": ["nerve"], "7.9 2.5 4.2": ["loop"], "2.2 21.0 5.8": ["sovereign"], "11.2 12.1 6.3": ["leaking"], "-2.2 14.5 3.3": ["prevail"], "4.7 10.5 3.4": ["sweat"], "-2.5 7.3 1.6": ["grassroots"], "3.9 9.3 1.0": ["slept"], "0.3 12.2 12.0": ["mortality"], "9.0 12.3 1.6": ["slogan"], "6.6 7.2 2.3": ["pipelines"], "-6.6 11.6 5.7": ["tempo"], "-4.6 -4.3 -0.6": ["counselor"], "5.3 11.3 9.5": ["shoots"], "21.1 16.5 14.4": ["kingdom"], "13.5 0.4 5.5": ["flurry"], "-7.1 13.8 -2.4": ["investigative"], "21.5 10.0 1.0": ["blockbuster"], "8.9 0.6 6.1": ["stir"], "-0.2 8.0 -2.6": ["constructive"], "6.6 8.5 -0.1": ["reinforce"], "12.0 2.0 4.5": ["labs"], "12.0 0.9 6.4": ["trailers"], "15.6 7.6 10.2": ["escalating"], "-8.1 5.4 18.2": ["rainy"], "10.5 7.8 6.3": ["tariffs"], "-1.7 3.3 -1.2": ["arraigned"], "-3.4 4.9 2.9": ["guitarist"], "9.1 3.4 35.3": ["vegetable"], "4.9 9.3 5.7": ["prefers"], "4.2 2.0 1.6": ["databases"], "14.5 13.3 11.1": ["bent"], "7.5 30.2 5.8": ["lethal"], "20.4 5.9 8.1": ["cluster"], "12.8 8.2 2.4": ["mergers"], "38.5 5.7 2.8": ["powerhouse"], "13.4 -1.3 0.1": ["rejects"], "12.3 -0.9 -1.5": ["manufactures"], "1.0 3.6 -2.7": ["collaborate"], "11.5 21.7 2.0": ["hazard"], "6.0 12.0 6.9": ["unofficial"], "2.1 10.7 4.7": ["lifelong"], "1.8 11.3 10.2": ["distress"], "11.5 -2.3 0.8": ["detailing"], "17.2 4.3 0.2": ["sensation"], "5.7 -1.0 1.8": ["vying"], "6.6 20.2 -3.0": ["blows"], "7.4 19.0 8.5": ["mob"], "4.1 11.2 4.8": ["calculations"], "21.6 16.4 9.8": ["crushing"], "1.1 8.2 3.2": ["incomplete"], "3.7 10.6 4.6": ["smartphones"], "21.1 5.3 17.7": ["sculpture"], "5.9 10.9 2.9": ["bloggers"], "-1.2 -2.2 -2.8": ["consulted"], "23.6 7.5 3.6": ["antitrust"], "10.1 -4.4 -2.1": ["royalties"], "-0.3 10.5 5.1": ["restraint"], "0.6 5.1 8.8": ["treasury"], "7.5 23.1 12.3": ["cruel"], "6.2 6.5 16.9": ["o"], "15.8 13.8 43.5": ["duck"], "-1.4 16.4 10.9": ["ceasefire"], "-0.1 -0.8 0.3": ["waiver"], "4.8 4.2 28.9": ["timber"], "1.5 3.3 9.4": ["needy"], "2.6 12.5 8.9": ["outfield"], "5.4 8.9 6.1": ["variable"], "11.1 -4.1 13.2": ["trimmed"], "20.7 9.6 3.8": ["waving"], "-0.1 17.9 2.3": ["readiness"], "-3.8 2.2 1.8": ["statutory"], "5.7 11.3 -2.1": ["safeguard"], "3.7 3.8 -5.5": ["testament"], "7.9 6.0 12.9": ["nickel"], "0.3 11.5 -0.6": ["ordeal"], "15.8 12.6 6.4": ["symbolic"], "11.0 10.6 2.5": ["goodwill"], "2.4 4.3 7.5": ["classical"], "9.3 28.6 5.6": ["destructive"], "9.6 0.6 3.6": ["kits"], "-2.1 16.8 5.1": ["ineffective"], "6.9 4.0 5.0": ["await"], "12.8 18.5 4.1": ["thrust"], "6.7 6.1 10.7": ["mixing"], "-5.7 12.3 -1.6": ["discharged"], "-0.2 3.6 6.2": ["metropolitan"], "8.4 22.3 3.3": ["strangers"], "2.4 16.1 0.1": ["paths"], "8.0 6.5 4.5": ["dynamics"], "5.6 0.4 -2.9": ["founders"], "2.6 8.4 14.4": ["sailed"], "-2.8 5.8 2.0": ["drafting"], "8.3 19.2 1.8": ["unite"], "1.5 24.4 5.7": ["factions"], "3.3 6.8 4.4": ["vague"], "1.0 9.4 2.3": ["repaired"], "-0.7 6.9 6.3": ["municipality"], "5.7 9.8 4.6": ["forgot"], "5.9 9.2 15.4": ["tastes"], "1.2 8.9 -0.8": ["interpreted"], "7.8 10.8 4.9": ["whistle"], "6.2 5.4 9.3": ["sensible"], "24.1 6.1 2.2": ["monopoly"], "0.3 2.1 2.7": ["backgrounds"], "3.7 1.6 5.2": ["streamline"], "11.0 -6.6 -2.0": ["advertised"], "14.7 11.6 -1.1": ["handy"], "-1.0 3.2 2.6": ["deterioration"], "7.2 10.8 4.4": ["spared"], "1.2 -0.2 2.0": ["progressed"], "17.0 8.1 2.1": ["displaying"], "-4.7 19.3 0.8": ["emergencies"], "0.4 20.2 7.7": ["subjective"], "5.8 5.0 3.1": ["goodbye"], "7.8 5.8 0.1": ["prohibits"], "-1.4 6.7 7.8": ["camping"], "0.8 0.6 7.0": ["accompany"], "-2.5 11.5 3.9": ["taxation"], "0.8 -2.0 7.0": ["tightened"], "-0.3 3.1 9.9": ["paired"], "17.9 2.8 6.7": ["toddler"], "9.4 6.2 1.8": ["strides"], "1.1 7.1 6.2": ["redemption"], "18.8 8.0 13.8": ["gentle"], "-4.8 6.3 4.9": ["gifted"], "14.6 5.3 3.0": ["bore"], "9.8 -2.5 3.1": ["originated"], "14.5 17.1 7.1": ["loser"], "10.1 15.3 5.4": ["pits"], "-2.7 -2.8 11.0": ["dresses"], "-3.6 9.4 4.5": ["intoxicated"], "-7.4 1.8 -2.0": ["contacting"], "18.7 15.4 26.5": ["underwater"], "4.3 8.8 4.2": ["closet"], "-0.4 8.9 3.7": ["fullback"], "11.2 18.8 10.4": ["viruses"], "0.5 -1.7 11.4": ["prep"], "-8.4 -3.3 2.0": ["enroll"], "0.5 4.6 8.5": ["overly"], "3.4 -1.1 7.4": ["prints"], "2.3 -5.0 10.3": ["visas"], "3.5 8.8 3.9": ["amnesty"], "3.3 1.0 4.9": ["rested"], "1.3 1.7 5.4": ["happier"], "-6.9 5.0 3.3": ["remarked"], "19.2 1.5 10.4": ["thriving"], "2.4 -1.1 6.3": ["spa"], "3.2 2.2 1.5": ["drowned"], "3.0 1.8 -0.9": ["invites"], "4.4 3.7 3.2": ["overdue"], "24.1 6.7 0.2": ["invented"], "13.1 -1.7 -1.3": ["saga"], "4.0 3.2 -1.0": ["stylish"], "2.4 -0.2 4.6": ["influx"], "-9.0 4.3 11.3": ["corrections"], "14.4 10.1 5.3": ["mapping"], "-0.7 6.7 4.2": ["broadcasts"], "13.7 4.4 15.6": ["stall"], "-4.1 3.9 1.8": ["composer"], "12.7 23.3 4.8": ["fronts"], "16.3 20.0 -1.3": ["secretly"], "10.6 5.6 14.9": ["crunch"], "5.3 9.0 16.0": ["scramble"], "12.5 -1.3 8.6": ["piled"], "6.8 -1.3 4.7": ["approvals"], "1.9 14.1 4.6": ["consciousness"], "7.3 5.8 -2.1": ["layout"], "-5.1 4.9 3.5": ["quoting"], "-7.4 4.2 7.7": ["abortions"], "13.0 10.8 0.4": ["backlash"], "7.7 3.5 10.6": ["obese"], "1.6 9.6 12.1": ["breakaway"], "16.1 4.8 0.6": ["bankrupt"], "3.2 -7.7 1.4": ["attracts"], "12.6 4.5 8.1": ["hammered"], "2.3 5.8 9.1": ["lesbian"], "1.6 14.6 8.0": ["realization"], "-1.2 0.8 -0.9": ["cites"], "8.3 13.1 17.5": ["endangered"], "-0.3 9.7 10.6": ["roadway"], "8.0 5.0 15.3": ["surfing"], "8.1 10.0 6.8": ["tenant"], "14.4 9.7 -2.4": ["proudly"], "7.1 16.3 5.5": ["endeavor"], "5.7 8.6 11.5": ["proteins"], "7.8 -2.7 10.0": ["lively"], "5.3 10.3 3.9": ["mechanics"], "12.6 8.3 6.8": ["accelerating"], "2.5 15.5 4.3": ["plots"], "-2.2 9.8 5.9": ["doubleheader"], "14.8 -7.9 -6.8": ["groundbreaking"], "11.2 0.3 0.8": ["advertise"], "1.9 17.9 5.5": ["intimidation"], "4.7 6.0 11.3": ["museums"], "1.7 -1.8 1.9": ["chairwoman"], "1.6 7.4 5.1": ["translation"], "3.5 -1.3 26.9": ["quota"], "-5.3 0.1 10.1": ["undergraduate"], "12.1 11.4 1.4": ["withstand"], "4.3 6.7 6.0": ["repurchase"], "4.9 8.8 5.2": ["preferences"], "2.6 -1.6 4.9": ["recommending"], "4.8 4.7 2.8": ["discourage"], "1.7 5.3 1.1": ["neglected"], "5.8 1.6 6.3": ["sprained"], "23.5 30.2 33.3": ["creatures"], "10.4 -7.8 10.0": ["catering"], "2.2 6.4 0.7": ["leveraging"], "2.2 15.7 10.3": ["cancers"], "15.7 -3.8 -2.0": ["consultancy"], "10.9 7.1 2.0": ["discovering"], "2.6 13.0 2.2": ["microphone"], "5.0 0.1 6.1": ["delaying"], "3.0 10.5 -1.2": ["withdrawing"], "-7.7 22.7 3.3": ["morale"], "2.4 5.9 10.1": ["sidewalks"], "18.9 6.0 10.1": ["balloon"], "-0.6 0.2 -5.2": ["warranty"], "12.3 -2.0 15.4": ["bucks"], "4.8 16.9 6.2": ["dilemma"], "9.1 1.5 -5.3": ["servicing"], "-3.5 18.0 11.5": ["troopers"], "12.2 9.4 26.7": ["eaten"], "14.1 10.0 7.0": ["ruin"], "-3.9 4.0 -1.8": ["inducted"], "3.8 12.9 5.1": ["govern"], "-4.0 7.8 10.0": ["prevailing"], "4.8 9.4 10.4": ["offs"], "-1.8 7.7 11.4": ["analog"], "3.9 13.9 -2.0": ["commanding"], "-0.7 5.2 -1.4": ["escorted", "tocomplete"], "-2.5 3.5 2.1": ["worthwhile"], "3.8 11.0 3.4": ["chooses"], "15.3 2.6 3.7": ["concession"], "8.7 0.2 5.7": ["sounding"], "7.4 7.3 9.8": ["insiders"], "-5.0 5.6 1.7": ["exceptionally"], "1.6 -0.3 -2.1": ["explored"], "2.0 9.5 5.9": ["genuinely"], "6.7 6.0 0.4": ["dreamed"], "6.6 5.7 7.1": ["paced"], "2.3 12.7 4.5": ["quarterfinal"], "4.4 13.9 22.2": ["sail"], "0.7 -5.8 5.1": ["supervised"], "7.6 4.6 -3.4": ["situated"], "9.9 20.7 6.6": ["skies"], "2.3 16.6 23.5": ["maritime"], "3.8 -4.1 1.1": ["wellness"], "-3.1 4.1 -0.4": ["exercised"], "0.9 14.7 6.6": ["probable"], "8.8 4.5 18.9": ["powder"], "9.1 12.9 -3.1": ["penetration"], "2.7 14.1 5.7": ["frankly"], "7.2 -3.7 1.4": ["comprise"], "2.0 10.8 6.6": ["unwilling"], "9.0 6.4 7.2": ["steering"], "-6.2 3.2 -6.3": ["def"], "5.0 8.9 -1.9": ["rallying"], "8.4 0.1 7.0": ["sanctioned"], "5.1 -0.8 2.2": ["auditorium"], "8.9 -4.7 4.2": ["earmarked"], "8.6 12.3 4.3": ["extract"], "9.0 1.3 -4.1": ["applauded"], "9.0 8.6 10.6": ["stride"], "-1.9 11.1 4.6": ["trusts"], "3.2 9.4 17.9": ["skating"], "-0.6 3.7 3.6": ["tackled"], "7.3 6.1 2.3": ["relocate"], "5.2 -1.4 1.5": ["bypass"], "4.1 4.2 2.0": ["deflected"], "4.9 12.7 4.9": ["smiled"], "11.4 11.5 7.5": ["impending"], "5.6 5.0 6.3": ["bath"], "1.0 6.5 -2.7": ["auditor"], "5.9 10.9 2.2": ["aka"], "7.6 1.9 4.0": ["commenced"], "-1.0 8.7 6.5": ["statistical"], "14.2 -5.8 5.1": ["packaged"], "8.5 4.3 8.0": ["gradual"], "-5.6 -2.1 8.9": ["prescriptions"], "8.0 1.9 11.8": ["mansion"], "2.2 17.0 6.0": ["accidental"], "-6.2 5.3 4.1": ["pointers"], "-5.4 0.8 11.6": ["collegiate"], "2.1 -2.8 5.9": ["enhancement"], "2.7 4.9 7.8": ["inclined"], "1.5 -3.2 1.3": ["clashed"], "7.6 -2.7 6.6": ["restitution"], "3.3 1.3 5.9": ["lieu"], "-5.8 7.1 11.2": ["irrigation"], "9.3 3.1 4.7": ["relocation", "drowns"], "12.8 0.5 10.1": ["porn"], "9.6 8.3 4.2": ["employing"], "-4.4 0.3 4.3": ["jeopardy"], "0.8 3.4 16.1": ["kidney"], "5.9 7.7 16.7": ["tagged"], "12.8 9.3 12.3": ["edges"], "-5.4 7.7 14.9": ["swimmers"], "-0.4 -1.9 7.7": ["enrichment"], "7.7 16.2 6.5": ["viewer"], "1.7 16.2 6.8": ["endure"], "16.0 8.6 4.9": ["tapping"], "7.6 -6.1 9.6": ["peaked"], "-1.1 13.2 -4.5": ["invaluable"], "15.0 -3.3 4.0": ["overshadowed"], "4.2 9.8 13.1": ["washing"], "15.1 6.9 2.9": ["halls"], "-3.1 12.2 6.7": ["callers"], "-1.1 -0.6 -1.3": ["revisions"], "5.8 8.0 8.2": ["rapper"], "6.4 1.1 3.1": ["traced"], "14.3 3.3 17.1": ["supermarkets"], "1.1 4.7 9.3": ["mandates"], "7.4 12.0 7.5": ["monument"], "4.4 5.9 5.1": ["timeout"], "9.6 21.6 9.0": ["cyber"], "22.1 13.5 13.4": ["dragging"], "9.7 8.2 4.7": ["resting"], "4.8 -3.2 17.5": ["dried"], "-2.2 6.9 4.3": ["parameters"], "6.2 7.2 5.9": ["straightforward"], "1.4 7.1 9.4": ["thread"], "5.2 8.5 1.6": ["demolished"], "3.1 0.4 -2.2": ["affirmed"], "3.8 14.7 8.5": ["fathers"], "-1.2 21.2 6.7": ["mindset"], "-1.5 9.6 1.3": ["regrets"], "15.0 -5.1 10.2": ["scaled"], "-4.9 8.7 0.1": ["impaired"], "7.0 8.6 -2.5": ["acknowledging"], "13.3 29.5 3.0": ["killers"], "-2.6 13.7 4.0": ["enforcing"], "-5.9 3.9 2.3": ["workouts"], "9.4 3.2 5.7": ["ins"], "22.0 8.0 31.1": ["pie"], "2.4 18.0 8.0": ["yelled"], "12.5 -1.0 2.0": ["rejecting"], "-3.3 1.3 4.5": ["deliberations"], "2.7 9.3 3.6": ["winless"], "2.8 8.7 9.6": ["yielding"], "21.2 6.1 -0.5": ["prototype"], "2.1 4.6 5.1": ["indicative"], "-0.8 16.0 1.1": ["irrelevant"], "11.6 18.9 7.8": ["sacred"], "-7.1 8.0 2.2": ["essay"], "-7.6 -4.7 -3.5": ["attends"], "6.6 25.9 1.1": ["bomber"], "5.4 3.5 -0.1": ["dealings"], "13.6 -0.0 15.4": ["cream"], "-1.8 -5.2 -0.2": ["waived"], "12.0 0.3 9.0": ["drawings"], "15.3 9.8 0.7": ["someday"], "8.1 9.1 0.9": ["murdering"], "5.0 3.0 5.1": ["fixtures"], "13.8 5.5 19.4": ["ecosystem"], "8.4 12.0 5.9": ["surfaces"], "9.1 3.1 9.9": ["textile"], "9.8 5.3 7.5": ["flipped"], "17.8 13.1 -0.3": ["swiftly"], "5.1 -5.3 2.3": ["editions"], "3.0 10.0 6.6": ["capitalized"], "4.7 -1.6 -1.7": ["introduces"], "27.6 10.5 0.7": ["multinational"], "15.2 9.0 14.2": ["gorgeous"], "-0.9 10.8 2.8": ["equalizer"], "20.9 18.0 17.5": ["bug"], "4.7 7.4 14.3": ["salvage"], "11.9 20.5 -2.0": ["plotting"], "9.2 3.6 16.7": ["pill"], "2.7 5.3 5.2": ["exceeds"], "13.8 41.0 6.0": ["foes"], "6.3 8.8 8.4": ["thermal"], "-1.0 -4.5 -5.3": ["professionally"], "14.2 11.9 19.3": ["cage"], "1.0 16.4 9.2": ["occurrence"], "-4.1 4.9 -4.7": ["educating"], "-2.0 -1.5 2.6": ["discusses"], "4.2 8.0 13.8": ["reservoir"], "7.1 13.6 5.8": ["accustomed"], "10.2 14.8 12.1": ["sanctuary"], "17.7 3.2 4.1": ["injunction"], "2.7 11.1 0.2": ["lungs"], "10.8 5.5 11.3": ["snacks"], "0.0 15.1 4.0": ["extradition"], "5.0 8.3 0.1": ["directive"], "1.4 7.9 3.1": ["optimal"], "11.6 13.8 12.1": ["shade"], "4.1 8.6 2.4": ["concentrating"], "2.3 7.6 2.8": ["eleven"], "11.7 11.6 -3.7": ["occupy"], "0.2 8.3 11.8": ["tourney"], "1.9 5.0 13.3": ["ensuing"], "0.9 3.4 10.5": ["referees"], "2.9 -5.4 3.5": ["resumes"], "-2.5 9.8 4.8": ["methodology"], "8.7 6.1 7.7": ["timed"], "8.6 22.1 -2.0": ["downed"], "-4.4 -2.8 6.8": ["bookings"], "-4.7 3.8 15.4": ["virtualization"], "4.5 2.1 11.8": ["trophies"], "-0.8 20.6 -1.1": ["communicating"], "-3.3 1.9 4.4": ["utilization"], "-0.6 0.3 5.1": ["inspected"], "4.5 25.1 9.8": ["yours"], "3.2 0.8 4.5": ["behavioral"], "-2.3 -0.3 0.0": ["sums"], "13.2 0.8 1.4": ["fueling"], "5.2 0.9 0.7": ["relocated"], "-3.0 6.0 5.5": ["congestion"], "2.5 8.3 2.0": ["architects"], "4.1 6.4 11.8": ["groin"], "11.1 1.7 3.4": ["southwestern"], "16.0 3.8 8.1": ["lackluster"], "2.6 17.2 10.5": ["corps"], "4.2 14.5 18.7": ["stones"], "-1.2 3.0 -2.0": ["contended"], "4.3 -4.1 1.5": ["hires"], "-4.7 -0.8 -3.0": ["consultations"], "5.9 12.5 1.3": ["depreciation"], "2.6 3.4 5.5": ["energetic"], "-0.6 5.4 5.2": ["corrected"], "-1.3 2.7 5.1": ["norm"], "14.8 13.0 16.6": ["bare"], "-0.8 5.6 -2.9": ["fulfilling"], "7.8 12.6 35.3": ["chickens"], "-2.5 9.9 6.2": ["prudent"], "6.3 21.5 7.4": ["siege"], "5.1 16.7 11.3": ["fearing"], "3.6 12.6 7.7": ["strains"], "-2.3 21.6 4.7": ["sergeant"], "0.4 15.4 11.0": ["realizes"], "12.5 0.6 5.0": ["scandals"], "7.7 10.0 10.7": ["countryside"], "10.1 -5.0 4.2": ["revived"], "3.0 12.2 7.8": ["cellphone"], "-2.6 0.6 4.6": ["repayment"], "1.6 9.7 6.8": ["diminished"], "4.8 10.9 5.9": ["gamble", "downsize"], "11.4 6.9 4.5": ["proliferation"], "13.4 -4.9 4.4": ["spanning"], "7.4 -2.7 1.2": ["rebate"], "17.4 -6.9 8.6": ["scrapped"], "8.2 7.6 2.9": ["manslaughter"], "-2.7 6.2 15.0": ["organs"], "3.4 1.7 -4.2": ["revelations"], "7.4 5.3 7.1": ["footer"], "2.5 4.2 6.0": ["luggage"], "7.6 13.4 3.2": ["smarter"], "6.4 4.8 5.4": ["recalling"], "7.6 12.6 9.2": ["misery"], "3.4 5.9 13.3": ["crisp"], "18.5 7.3 5.9": ["mock"], "1.5 12.0 2.7": ["legitimacy"], "18.4 2.5 15.1": ["biotech"], "-1.1 -0.6 1.5": ["revision"], "13.6 -2.2 2.6": ["faded"], "10.8 2.0 1.8": ["improperly"], "9.4 7.9 -0.2": ["revelation"], "8.5 -1.7 3.1": ["winding"], "-6.1 20.8 2.9": ["sacrifices"], "5.4 -1.5 7.8": ["consisted"], "13.0 7.8 2.7": ["vacuum"], "5.8 7.6 7.6": ["definite"], "6.6 2.8 -1.7": ["resolving"], "3.3 10.8 9.9": ["blockade"], "-2.0 15.9 3.1": ["imprisoned"], "6.4 -1.5 3.9": ["registry"], "5.4 6.1 5.2": ["measurements"], "-7.8 11.0 3.5": ["fielding"], "14.3 3.8 0.5": ["undisclosed"], "2.3 8.4 11.6": ["diamonds"], "-4.7 0.5 3.0": ["surgeries"], "10.6 4.8 2.3": ["rampant"], "19.7 7.3 15.2": ["cartoon"], "1.2 4.1 13.4": ["cab"], "-8.0 3.5 -2.8": ["mileage"], "4.1 13.5 0.3": ["proposition"], "12.4 0.3 5.3": ["predominantly"], "5.8 6.5 -0.1": ["reinforced"], "7.8 5.9 29.3": ["waterfront"], "-1.4 10.2 -1.0": ["exercising"], "-0.0 17.3 8.9": ["realities"], "-1.4 19.3 0.3": ["unconscious"], "3.2 6.8 -2.2": ["exploited"], "9.1 26.8 3.4": ["hated"], "-4.6 2.7 -3.9": ["campaigned"], "8.7 7.6 7.8": ["postal"], "5.6 -4.0 3.7": ["rebates"], "14.6 3.8 13.6": ["juice"], "-1.2 19.1 3.8": ["anytime"], "3.7 1.7 -5.0": ["extensively"], "2.8 7.7 2.7": ["greet"], "2.8 11.0 8.8": ["remedy"], "-1.3 4.0 3.0": ["thoughtful"], "16.0 3.6 -2.1": ["banners"], "14.8 10.5 8.3": ["lobbyist"], "0.9 7.0 4.2": ["defines"], "-5.0 10.3 2.7": ["deported"], "-3.5 4.5 4.9": ["fouls"], "8.5 14.7 18.1": ["bureaucracy"], "1.3 8.3 1.6": ["interactions"], "3.9 18.7 7.1": ["malaria"], "7.6 5.8 37.4": ["salad"], "-5.4 9.0 4.5": ["consolation"], "4.6 3.6 4.9": ["inspect"], "11.8 0.3 9.9": ["slapped"], "5.6 -2.9 15.6": ["festive"], "-6.7 6.5 6.0": ["prostitution"], "2.8 5.4 10.1": ["varying"], "8.2 6.1 -2.4": ["etc"], "1.0 2.7 -3.3": ["compliant"], "16.3 -2.3 9.6": ["floated"], "0.2 17.5 9.7": ["batsmen"], "0.3 16.5 3.8": ["asleep"], "21.8 9.9 -2.0": ["transforming"], "6.4 9.1 0.5": ["idle"], "3.0 8.6 4.6": ["newcomer"], "-2.7 11.2 5.7": ["legislator"], "14.0 7.2 2.1": ["generator"], "5.4 6.5 2.3": ["hydrogen"], "16.2 0.0 7.7": ["overturn"], "12.7 0.8 6.3": ["outfits"], "12.8 14.1 11.0": ["puzzle"], "-6.3 5.3 9.8": ["recount"], "17.9 15.3 10.6": ["famously"], "-2.2 12.4 -0.9": ["stairs"], "4.0 -5.7 -3.8": ["petitions"], "15.2 11.1 2.1": ["unspecified"], "4.6 15.7 18.8": ["settlers"], "7.9 8.6 7.8": ["couch"], "-5.9 -0.2 -0.2": ["vacancy"], "-4.3 1.1 18.7": ["condo"], "0.9 13.4 -3.6": ["condemn"], "7.0 7.0 7.1": ["laundry"], "4.4 7.7 8.5": ["worsening"], "12.9 23.1 9.8": ["damn"], "24.4 0.2 6.6": ["whopping"], "8.9 -2.7 0.3": ["injected"], "14.8 5.5 11.4": ["cafe"], "13.4 4.2 7.7": ["glance"], "0.8 8.3 13.0": ["permitting"], "3.0 -9.7 -0.7": ["cater"], "9.1 2.8 1.2": ["northwestern"], "8.6 3.8 7.9": ["rein"], "2.8 14.4 6.8": ["crosses"], "-2.6 8.2 3.8": ["desirable"], "3.5 20.6 5.4": ["occupants"], "5.7 16.0 7.5": ["hedge"], "10.7 22.0 0.8": ["hazards"], "9.0 2.7 5.0": ["ink"], "5.1 9.4 10.9": ["nail"], "4.9 7.5 4.9": ["rendered"], "-2.5 7.8 7.3": ["fielder"], "10.5 6.1 -0.2": ["optimized"], "0.3 13.5 1.6": ["understandable"], "5.9 2.5 4.6": ["moms"], "-0.5 11.5 8.9": ["mitigate"], "3.5 10.0 -0.4": ["abide"], "16.8 2.2 -2.5": ["advertisement"], "3.3 5.9 6.0": ["kicker", "intervertebral"], "1.1 -4.7 4.6": ["intake"], "10.2 8.1 40.5": ["soup"], "0.1 9.2 0.7": ["precautions"], "0.1 13.1 2.1": ["problematic"], "9.7 -6.9 6.2": ["wraps"], "-3.4 2.2 1.8": ["incidence"], "-2.3 6.2 -2.7": ["conditioning"], "-4.1 3.1 -3.2": ["collateral"], "6.0 20.3 5.1": ["airplanes"], "-4.3 10.6 -1.1": ["enlisted"], "3.5 8.1 10.8": ["bishop"], "6.0 16.2 6.7": ["reckless"], "13.8 0.3 4.6": ["completes"], "0.5 1.4 -2.7": ["researching"], "2.7 9.0 6.7": ["bearish"], "7.8 7.9 7.1": ["constitutes"], "8.1 -3.3 7.8": ["tab"], "3.3 -5.2 1.3": ["postpone"], "-1.4 8.5 8.8": ["grounder"], "20.1 -9.7 -6.7": ["pioneering"], "2.2 2.5 7.7": ["theatrical"], "8.9 1.2 -0.4": ["lounge"], "0.2 3.4 3.4": ["termed"], "4.1 16.6 13.7": ["pandemic"], "4.9 13.9 11.0": ["annualized"], "-3.6 10.9 37.1": ["anglers"], "13.1 5.7 2.0": ["heights"], "0.0 9.5 -0.0": ["convey"], "13.2 7.8 1.1": ["generators"], "11.5 9.6 4.6": ["exploitation"], "13.0 4.1 -2.1": ["gateway"], "11.1 -3.6 1.6": ["viability"], "21.0 3.1 6.9": ["slew"], "11.8 31.0 10.3": ["vicious"], "8.4 -3.0 -1.6": ["incorporates"], "8.4 14.7 6.2": ["absurd"], "13.2 15.5 5.0": ["pounded"], "-0.0 11.3 5.1": ["gospel"], "9.1 9.3 29.1": ["barbecue"], "-2.6 7.9 6.7": ["sentiments"], "7.2 20.7 10.0": ["dare"], "-0.9 13.8 5.3": ["lens"], "2.4 12.7 5.4": ["behaviors"], "-15.6 22.4 -0.5": ["interrogation"], "8.6 2.9 3.7": ["blankets"], "10.0 9.4 8.9": ["demo"], "4.2 5.0 7.1": ["trunk"], "-8.3 4.3 8.8": ["vocals"], "1.1 5.8 4.3": ["coordinating"], "-3.4 4.8 -2.2": ["responsive"], "5.2 1.5 15.8": ["mercury"], "5.9 22.2 3.1": ["commands"], "8.6 12.8 -2.4": ["exposing"], "4.8 6.0 4.8": ["relieve"], "14.9 11.8 5.8": ["obsessed"], "14.7 16.8 13.8": ["masters"], "-1.4 8.3 -0.8": ["identifies"], "-6.6 1.2 -1.4": ["volunteering"], "1.3 9.3 -5.2": ["accessing"], "35.1 6.0 3.7": ["billionaire"], "0.6 0.6 7.3": ["refined"], "7.7 6.4 0.2": ["generosity"], "14.0 14.8 20.9": ["eagle"], "-3.1 5.5 3.2": ["doubtful"], "-1.2 4.4 0.6": ["avenues"], "8.8 1.5 3.2": ["optimization"], "-1.2 3.3 4.7": ["autonomy"], "7.5 -6.8 0.1": ["arose"], "15.5 16.1 6.9": ["wipe"], "3.7 15.9 3.7": ["executing"], "1.8 7.9 1.2": ["precaution"], "8.8 12.3 10.0": ["marker"], "1.1 9.9 11.2": ["erosion"], "10.3 18.7 9.2": ["elusive"], "10.9 6.7 -0.0": ["restructure"], "7.0 7.6 9.5": ["paralyzed"], "-1.5 10.0 -2.5": ["abduction"], "1.4 -1.6 -3.2": ["acclaimed"], "17.4 1.5 8.3": ["circus"], "10.1 7.3 9.6": ["proceeded"], "11.9 13.8 3.9": ["dimension"], "0.6 1.9 -3.0": ["allege"], "1.1 6.0 5.4": ["robberies"], "3.6 4.7 6.5": ["translates"], "-1.4 18.0 8.6": ["punches"], "12.6 1.5 3.6": ["tablets"], "6.8 5.1 3.8": ["parcel"], "-8.5 6.8 4.1": ["chapters"], "16.5 5.1 -0.6": ["bio"], "29.3 1.0 5.4": ["laden"], "15.9 4.6 5.4": ["rattled"], "1.3 6.2 8.9": ["switches"], "2.8 49.3 4.6": ["battlefield"], "11.0 3.1 4.4": ["splitting"], "13.2 6.6 9.6": ["reeling"], "14.5 1.2 4.6": ["terminals"], "3.0 6.9 20.5": ["coins"], "-4.4 5.5 16.9": ["delegate"], "13.8 11.8 11.0": ["doomed"], "1.0 1.3 3.3": ["conducts"], "9.1 12.3 -0.9": ["absorbed"], "0.3 6.4 12.9": ["organ"], "-0.1 4.1 2.1": ["adhere"], "3.3 0.4 11.3": ["dressing"], "0.1 12.7 -0.8": ["assertion"], "9.9 5.7 8.2": ["carpet"], "19.3 17.8 3.4": ["unleashed"], "6.6 5.1 2.1": ["outraged"], "14.5 2.0 -0.9": ["widened"], "9.7 -1.6 5.7": ["flagged"], "16.2 4.3 4.9": ["reminiscent"], "11.2 14.3 4.8": ["remake"], "9.1 5.5 10.6": ["beverages"], "4.7 14.3 6.0": ["equation"], "7.7 5.5 17.1": ["bingo"], "15.0 3.9 8.9": ["bleak"], "18.5 1.3 10.5": ["plummeted"], "8.6 8.8 8.0": ["tariff"], "10.2 10.5 -2.7": ["rugged"], "7.9 16.1 7.6": ["devastation"], "13.1 2.7 9.5": ["squeezed"], "2.5 -3.3 -0.1": ["screenings"], "9.6 -5.5 14.1": ["gala"], "8.3 4.0 25.3": ["beans"], "8.7 1.2 1.7": ["speculated"], "-0.5 17.9 3.0": ["checkpoints"], "2.4 17.4 2.9": ["malicious"], "9.3 5.4 6.0": ["pads"], "7.6 13.5 3.1": ["distracted"], "-8.9 -2.4 4.2": ["residency"], "5.9 20.7 10.8": ["mercy"], "3.9 1.5 4.7": ["remarkably"], "14.2 13.8 9.5": ["smash"], "2.1 7.6 3.2": ["boarded"], "4.8 10.2 -2.7": ["aligned"], "-4.9 7.6 3.6": ["disagreement"], "3.4 9.1 8.4": ["graffiti"], "-7.0 5.7 4.6": ["belongings"], "12.7 7.6 14.5": ["environmentalists"], "-0.7 15.0 11.5": ["slavery"], "9.0 14.7 9.8": ["retrieve"], "5.8 -2.3 -2.5": ["undergone"], "7.6 8.1 2.0": ["aisle"], "16.2 9.7 12.2": ["happily"], "3.4 2.0 7.9": ["crafted"], "16.7 4.2 2.8": ["ventures"], "3.1 20.1 6.5": ["encounters"], "9.3 7.6 71.7": ["shrimp"], "38.5 27.7 10.2": ["mighty"], "4.4 9.9 8.4": ["policymakers"], "-2.8 8.3 7.1": ["drainage"], "5.6 4.8 15.1": ["establishments"], "18.4 4.1 10.0": ["carved"], "2.6 3.3 4.8": ["placebo"], "2.5 18.3 11.9": ["irony"], "3.9 7.4 4.9": ["drastically"], "4.2 -0.6 -1.7": ["publishes"], "9.7 17.8 5.3": ["annoying"], "1.8 9.2 4.2": ["mourning"], "20.5 8.3 13.3": ["bell"], "5.1 3.8 0.1": ["cruised"], "0.0 7.8 2.7": ["sufficiently"], "22.5 5.1 0.6": ["toppled"], "-5.5 9.9 5.0": ["qualifiers"], "-0.8 6.4 0.0": ["disorders"], "-4.4 8.7 11.8": ["motorcycles"], "-2.0 0.3 3.9": ["cite"], "5.5 -3.3 6.0": ["nearing"], "3.0 10.8 -0.7": ["responds"], "-6.0 9.7 6.8": ["aggravated"], "17.1 8.7 3.5": ["rows"], "-1.8 7.1 40.4": ["tomatoes"], "10.5 17.1 11.7": ["spray"], "4.4 4.9 0.7": ["modify"], "5.5 -0.5 4.8": ["alleviate"], "6.6 14.3 7.0": ["easiest"], "8.2 5.6 2.3": ["erased"], "-2.5 3.4 9.5": ["distressed"], "4.1 4.9 -1.4": ["authorize"], "3.0 4.3 3.4": ["liters"], "5.4 9.4 11.1": ["eurozone"], "-4.6 8.5 8.1": ["poet"], "2.9 5.7 5.9": ["applicant"], "-1.9 19.2 7.2": ["probability"], "-4.6 7.4 -4.1": ["affiliation"], "-3.7 8.8 -6.0": ["empower"], "3.1 7.3 4.8": ["landslide"], "1.8 17.2 10.0": ["calculation"], "4.3 11.9 7.4": ["upstairs"], "5.7 12.8 7.3": ["yeah"], "3.4 3.6 -1.9": ["breadth"], "3.8 3.6 -1.5": ["breached"], "1.4 7.5 7.0": ["tended"], "-0.1 9.6 17.6": ["reactors"], "8.0 -3.0 -0.6": ["incorporating"], "-8.2 3.7 9.3": ["marriages"], "-4.3 3.8 7.3": ["curfew"], "3.6 11.2 34.3": ["sauce"], "7.4 15.3 9.9": ["flick"], "14.2 10.8 11.9": ["merchant"], "12.0 19.2 -0.0": ["frightening"], "1.5 5.0 1.5": ["prevalent"], "5.1 -4.9 -1.1": ["distributes"], "5.5 6.8 3.3": ["collector"], "8.2 4.4 1.1": ["congress"], "6.4 6.7 -0.3": ["boast"], "6.7 9.1 4.5": ["nevertheless"], "1.4 5.5 6.4": ["drummer"], "2.3 14.3 -1.3": ["scouting"], "8.5 8.6 12.0": ["heavier"], "-5.8 5.5 9.8": ["wrestlers"], "0.5 -3.7 -3.3": ["retains"], "13.4 12.9 8.5": ["globalization"], "3.4 3.3 5.4": ["subdued"], "8.2 5.6 7.6": ["bruised"], "-4.2 12.1 -0.9": ["respectful"], "6.6 13.8 -1.9": ["cult"], "11.6 14.1 8.9": ["twisted"], "9.4 23.0 10.0": ["myth"], "2.9 17.6 7.8": ["survivor"], "-2.0 0.2 3.1": ["ensemble"], "-3.5 -0.6 4.0": ["deadlock"], "-1.0 11.3 3.4": ["governed"], "10.4 0.5 17.1": ["cafeteria"], "4.9 3.5 -0.6": ["auditors"], "3.5 8.7 8.1": ["harmony"], "0.9 6.5 1.6": ["uncommon"], "1.6 8.1 8.9": ["moisture"], "8.0 14.3 12.1": ["spacecraft"], "15.2 19.7 4.0": ["gravity"], "5.2 7.1 10.4": ["swelling"], "-2.7 7.1 4.4": ["prevailed"], "9.4 -0.5 0.2": ["seamless"], "1.2 4.8 7.6": ["serial"], "8.7 24.3 8.1": ["mortar"], "1.7 -2.5 7.4": ["archived"], "12.9 28.6 13.5": ["aerial"], "2.1 4.8 11.9": ["artifacts"], "6.8 13.0 3.9": ["hail"], "4.7 1.7 2.5": ["prolific"], "2.2 -5.7 0.5": ["finalize"], "6.3 24.8 3.8": ["destiny"], "16.1 9.1 11.6": ["poles"], "-3.4 -2.9 -5.4": ["mediation"], "9.0 8.6 13.9": ["sunshine"], "3.5 -2.9 -1.9": ["extensions"], "0.9 7.0 4.6": ["collectors"], "11.3 13.9 1.6": ["headache"], "8.0 8.7 21.3": ["derby"], "6.2 5.3 6.0": ["dancer"], "6.5 9.8 10.4": ["brace"], "2.4 8.1 2.5": ["vandalism"], "-1.9 6.9 -0.2": ["privileged"], "0.2 19.9 10.3": ["justification"], "10.5 18.9 16.4": ["butt"], "9.5 8.7 11.4": ["rim"], "13.5 10.3 6.6": ["un"], "7.6 1.3 2.8": ["gearing"], "-0.2 18.9 6.0": ["freedoms"], "2.3 4.9 11.3": ["canal"], "-5.9 14.7 1.7": ["honesty"], "7.9 3.8 2.2": ["confiscated"], "11.6 4.0 7.0": ["bribery"], "2.5 2.5 9.5": ["recurring"], "17.4 19.1 8.6": ["retreated"], "0.8 -2.3 7.8": ["passports"], "18.0 -1.4 9.5": ["startup"], "9.6 12.4 0.5": ["simulation"], "-1.8 -0.7 8.0": ["rents"], "2.3 11.9 29.6": ["dessert"], "3.3 -5.4 6.2": ["skipped"], "4.7 1.0 -1.5": ["captures"], "-2.0 4.4 7.1": ["underwriting"], "2.7 1.0 -6.0": ["congratulate"], "1.5 7.3 0.6": ["advancement"], "-5.3 2.0 0.3": ["psychiatric"], "0.1 34.6 -4.2": ["extremist"], "3.9 6.7 4.6": ["blames"], "-2.4 5.9 11.4": ["freestyle"], "-5.2 6.3 7.3": ["rookies"], "10.9 15.8 6.8": ["combinations"], "7.4 7.9 6.9": ["framed"], "-2.6 0.2 -1.0": ["archives"], "19.9 16.3 8.7": ["shapes"], "0.8 2.9 3.5": ["privileges", "thapsigargin"], "18.6 5.9 0.3": ["technician"], "11.4 7.4 3.8": ["mirrors"], "16.0 6.5 10.6": ["slashing"], "10.3 0.9 -4.9": ["traces"], "14.2 12.6 1.6": ["resilient"], "-6.3 5.5 -2.6": ["expelled"], "-3.0 5.7 1.0": ["interval"], "5.1 14.4 2.2": ["secrecy"], "-3.3 29.1 6.5": ["ideological"], "16.6 6.4 3.8": ["banker"], "7.1 7.6 10.1": ["landlord"], "11.4 4.8 6.4": ["labeling"], "-4.3 19.7 -3.7": ["assaults"], "2.5 3.4 1.3": ["barring"], "9.2 3.5 29.9": ["sandwich"], "11.6 0.8 9.5": ["hauled"], "3.7 11.3 1.8": ["peacefully"], "13.9 9.0 5.3": ["bidder"], "2.5 6.2 10.0": ["progression"], "17.9 15.1 16.6": ["shores"], "5.6 1.4 8.2": ["maiden"], "7.7 0.6 0.7": ["simplify"], "-8.2 12.8 14.2": ["antibiotics"], "5.5 9.6 -0.6": ["proximity"], "6.8 10.5 14.8": ["accent"], "5.0 9.5 6.1": ["soundtrack"], "0.0 3.4 -1.5": ["fulfilled"], "3.5 3.8 14.9": ["locks"], "3.8 -2.8 20.7": ["calf"], "-2.3 7.1 10.0": ["jurisdictions"], "4.0 12.2 -2.4": ["portray"], "6.2 9.7 4.5": ["wasting"], "5.8 18.0 11.7": ["gotta"], "-0.5 8.4 5.5": ["drained"], "5.8 1.7 -2.6": ["paved"], "5.3 12.2 2.6": ["forge"], "5.9 2.7 3.8": ["induced"], "-8.3 10.9 1.7": ["deployments"], "9.2 2.8 -1.9": ["footsteps"], "6.3 2.7 5.5": ["appliance"], "1.8 7.1 9.8": ["anticipating"], "7.0 10.8 7.4": ["calculate"], "3.6 8.3 5.9": ["relegation"], "1.4 9.7 19.2": ["coin"], "-3.0 2.9 6.1": ["preceding"], "13.3 19.7 8.3": ["pretend"], "7.8 1.5 12.6": ["downstream"], "5.8 4.4 5.6": ["printer"], "10.8 9.2 5.6": ["tandem"], "3.5 13.3 6.4": ["rebuilt"], "23.7 -0.1 0.8": ["unveiling"], "-1.5 1.7 6.3": ["protocols"], "5.6 12.6 0.2": ["marginal"], "10.8 6.0 11.1": ["descent"], "13.6 4.3 28.5": ["nets"], "-4.7 9.5 6.8": ["hardship"], "3.3 8.5 -0.4": ["classification"], "2.1 6.3 7.9": ["hiking"], "7.2 2.5 2.5": ["fortnight"], "12.2 9.1 3.3": ["poisoning"], "7.4 4.9 -2.3": ["defends"], "8.1 14.2 2.4": ["outdated"], "4.2 16.6 3.9": ["indoors"], "5.9 0.5 4.5": ["commercially"], "2.1 9.2 1.8": ["scouts"], "9.6 18.3 11.3": ["satellites"], "-2.6 6.8 5.1": ["selective"], "1.4 17.8 3.9": ["dear"], "2.2 21.2 -2.5": ["scout"], "8.1 8.0 9.2": ["blogger"], "-3.4 3.7 9.1": ["motel"], "8.9 13.0 14.3": ["phrases"], "0.6 3.9 3.2": ["yoga"], "6.8 9.5 -0.1": ["guiding"], "12.1 11.0 8.4": ["backbone"], "0.8 20.5 1.9": ["dispatch"], "-2.2 2.3 25.9": ["chefs"], "2.2 -1.5 -1.4": ["memorandum"], "23.6 13.3 28.0": ["elephant"], "6.0 9.9 10.9": ["pilgrims"], "7.1 6.7 3.8": ["chaotic"], "0.5 16.8 2.0": ["forgive"], "-4.2 4.9 4.4": ["scholar"], "-2.3 8.2 8.4": ["decreasing"], "11.7 14.4 0.3": ["fundamentally"], "7.0 9.5 11.5": ["abundance"], "-0.8 6.8 8.4": ["enact"], "5.0 8.7 -3.1": ["controllers"], "6.6 15.0 -0.4": ["hazardous"], "6.4 4.5 4.7": ["granddaughter"], "-2.0 10.1 17.3": ["captains"], "1.7 16.6 1.5": ["surroundings"], "3.7 6.1 3.2": ["contraction"], "2.1 21.4 15.0": ["trooper"], "1.2 -0.3 2.1": ["envelope"], "-0.8 3.5 8.0": ["diocese"], "23.9 3.7 8.8": ["bouncing"], "23.6 9.8 3.5": ["exporter"], "9.7 6.4 6.9": ["awaits"], "-8.7 6.7 -0.5": ["stresses"], "13.3 12.4 14.6": ["slap"], "5.2 1.9 -0.6": ["disruptions"], "10.2 14.4 27.1": ["flesh"], "13.0 11.2 3.4": ["daunting"], "-0.5 7.0 2.8": ["reunited"], "-5.7 8.0 1.0": ["novels"], "-8.2 -4.5 2.0": ["reinstated"], "3.6 5.5 16.4": ["ash"], "14.1 8.5 10.8": ["brass"], "17.5 10.8 8.2": ["myriad"], "14.4 16.1 6.7": ["ravaged"], "0.5 6.9 2.5": ["motions"], "2.3 9.9 7.1": ["goaltender"], "16.2 3.8 2.2": ["stumbled"], "-4.1 3.5 -4.1": ["polled"], "1.2 4.3 5.9": ["planner"], "-5.3 13.4 -0.1": ["bargaining"], "12.0 16.1 14.4": ["palace"], "-2.6 -0.0 11.0": ["jewelery"], "11.4 4.2 6.8": ["pour"], "-4.4 7.9 12.0": ["clergy"], "0.2 11.7 8.7": ["independents"], "-5.6 -2.6 -7.3": ["accredited"], "4.8 16.4 7.4": ["pedestrians"], "-5.4 6.4 6.7": ["commute"], "4.4 6.2 2.7": ["clearer"], "5.4 7.3 8.6": ["balancing"], "-2.7 -5.5 0.2": ["presided"], "3.4 11.0 8.3": ["scarce"], "12.6 13.2 17.3": ["tropical"], "3.1 8.2 9.3": ["interstate"], "-1.2 11.4 0.5": ["sympathetic"], "26.6 9.2 15.5": ["slumping"], "15.6 15.5 4.1": ["realm"], "0.6 11.6 9.9": ["umpire"], "1.4 7.3 3.9": ["inflammation"], "9.5 3.8 -0.3": ["laboratories"], "-0.7 8.0 14.1": ["sewage"], "0.3 9.7 12.7": ["pavement"], "-1.7 6.8 8.7": ["sanitation"], "-2.3 1.4 8.9": ["quantities"], "7.2 8.9 -0.7": ["remotely"], "14.7 9.1 9.0": ["blueprint"], "10.4 -1.0 7.5": ["coupons"], "0.6 13.9 8.7": ["dictate"], "6.5 22.5 7.1": ["underdog"], "17.5 15.1 2.7": ["captive"], "4.9 5.8 7.4": ["asbestos"], "6.7 4.5 -0.4": ["durable"], "6.6 7.5 1.1": ["headaches"], "1.4 7.5 -1.8": ["gratitude"], "-2.9 1.3 2.8": ["deleted"], "-1.8 1.1 6.4": ["stoppage"], "8.8 2.6 1.5": ["convertible"], "-5.7 15.3 8.4": ["spouses"], "5.8 6.6 9.0": ["exported"], "5.0 6.3 1.7": ["orientation"], "14.1 7.8 4.2": ["origins"], "6.9 9.3 -0.1": ["accountant"], "6.8 3.8 8.7": ["graders"], "15.7 6.8 8.1": ["patches"], "15.1 3.8 7.8": ["cart"], "12.1 7.1 9.9": ["triggering"], "4.3 6.3 6.8": ["classics"], "4.3 1.8 4.2": ["farewell"], "3.1 -4.2 2.0": ["rulings"], "-2.7 2.3 3.4": ["refinancing"], "7.0 7.0 6.1": ["commentator"], "1.1 7.8 7.5": ["lips"], "7.7 7.8 0.1": ["photographed"], "10.1 15.2 12.8": ["ropes"], "2.8 2.4 0.2": ["eliminates"], "4.1 7.7 1.5": ["spirited"], "-6.9 2.7 -2.0": ["fielded"], "7.5 -6.5 4.7": ["marred"], "5.2 5.7 4.0": ["acceleration"], "7.8 3.9 -4.6": ["centralized"], "13.6 9.9 -0.2": ["embracing"], "2.2 13.9 2.5": ["rightly"], "2.8 15.2 12.4": ["rational"], "9.1 7.8 11.0": ["scrambled"], "7.0 1.2 -0.6": ["thumbs"], "5.6 23.9 39.5": ["bait"], "16.1 22.3 16.0": ["bugs"], "10.7 8.8 13.8": ["minerals"], "0.4 -1.2 -2.5": ["cardiovascular"], "-4.9 -0.1 -2.7": ["interviewing"], "6.9 8.5 7.9": ["tales"], "1.4 1.9 4.7": ["conditional"], "9.6 0.1 -0.2": ["sensational"], "0.4 6.1 6.2": ["asylum"], "6.5 11.9 0.0": ["setbacks"], "-4.7 14.1 7.2": ["dissent"], "1.3 12.5 -0.1": ["repeating"], "5.3 2.9 8.0": ["conventions"], "-1.3 10.7 5.0": ["susceptible"], "7.8 6.4 3.0": ["burnt"], "6.4 4.4 10.1": ["sloppy"], "-2.9 0.8 -9.2": ["commended"], "3.1 1.8 -6.6": ["unanswered"], "-0.8 13.2 7.4": ["remark"], "-1.3 -1.7 -3.0": ["exhibited"], "9.8 3.9 -1.9": ["reassure"], "11.1 8.2 29.4": ["pigs"], "17.0 2.5 -3.2": ["revamped"], "0.2 7.6 4.8": ["metrics"], "11.3 18.3 9.0": ["thrill"], "3.8 6.7 9.0": ["charming"], "9.7 28.5 13.5": ["buddy"], "8.2 8.5 7.6": ["skepticism"], "7.1 16.4 6.9": ["adventures"], "12.7 4.1 4.9": ["inexpensive"], "6.4 9.1 4.0": ["hints"], "25.1 4.2 10.1": ["centerpiece"], "-1.1 18.4 11.8": ["offender"], "9.1 -1.3 0.9": ["complimentary"], "6.3 0.5 3.5": ["respectable"], "14.8 2.0 14.6": ["cans"], "7.2 3.0 3.1": ["buzzer"], "10.4 -0.0 4.0": ["vanished"], "9.2 10.3 21.1": ["yacht"], "-1.6 1.1 -1.3": ["modifications"], "21.3 7.3 36.3": ["pig"], "17.2 -1.4 5.2": ["sparking"], "0.6 14.4 5.6": ["terribly"], "3.8 1.1 -0.5": ["broaden"], "-3.6 5.9 3.3": ["withheld"], "7.8 -1.5 6.8": ["soap"], "-0.7 9.7 4.3": ["paramedics"], "-1.9 16.1 3.5": ["suspicions"], "12.9 2.7 14.9": ["rack"], "-5.2 6.8 0.6": ["sincere"], "-5.2 5.5 8.9": ["supplemental"], "4.1 4.3 7.8": ["entirety"], "8.2 8.0 5.9": ["commentators"], "1.5 3.6 0.6": ["similarities"], "12.5 22.7 11.4": ["bunker"], "16.1 17.7 2.8": ["pounding"], "8.0 4.4 1.8": ["whereby"], "18.0 -0.0 7.7": ["blowout"], "-5.5 10.6 2.0": ["instructors"], "-0.5 3.6 8.4": ["intermediate"], "11.2 -3.1 3.5": ["subsidized"], "19.8 0.2 4.1": ["frenzy"], "18.6 18.8 19.4": ["ghost"], "-2.1 18.0 -2.1": ["virtue"], "8.9 7.9 1.8": ["chancellor"], "6.1 3.5 2.4": ["thefts"], "26.4 8.1 1.3": ["embattled"], "-2.1 2.7 6.0": ["penalized"], "9.5 -6.1 -0.1": ["pave"], "-4.0 6.5 -2.0": ["uphold"], "4.7 14.2 8.4": ["guessing"], "6.4 10.9 9.2": ["onboard"], "11.8 7.6 10.4": ["stacked"], "1.1 3.5 3.6": ["progressing"], "1.2 0.6 -2.0": ["magistrate"], "5.3 1.7 0.8": ["discoveries"], "1.0 42.8 12.3": ["artillery"], "12.6 -4.6 8.8": ["wrapping"], "13.2 -1.2 -2.2": ["ignited"], "11.7 2.3 5.6": ["illustrate"], "10.1 7.0 8.3": ["wires"], "9.3 1.4 2.2": ["fills"], "0.5 7.8 3.6": ["mm"], "-0.6 2.8 3.8": ["practitioners", "notlimited"], "4.2 3.2 39.9": ["potatoes"], "3.1 13.4 16.6": ["slaughter"], "5.8 4.8 2.7": ["envisioned"], "5.2 9.4 10.4": ["ransom"], "-4.9 18.8 12.3": ["pistol"], "-1.8 -1.4 2.1": ["satisfactory"], "11.0 11.0 12.1": ["grind"], "2.0 1.6 20.3": ["banquet"], "13.1 5.2 2.7": ["excludes"], "1.2 -2.2 -0.7": ["lectures"], "6.4 6.8 -1.4": ["breaches"], "7.2 10.8 12.0": ["skull"], "-3.1 5.7 3.4": ["conflicting"], "1.5 10.1 -4.0": ["transmitted"], "3.7 8.9 1.8": ["behave"], "1.5 6.2 1.2": ["refreshing"], "2.6 8.2 -3.0": ["cumulative"], "6.0 8.3 12.4": ["hilarious"], "9.8 18.3 10.0": ["fool"], "3.7 9.5 0.3": ["incremental"], "13.5 9.3 9.0": ["refining"], "-7.0 7.2 -3.1": ["liaison"], "-2.7 -1.9 6.4": ["evenings"], "8.4 10.4 2.5": ["transporting"], "7.4 7.7 8.4": ["beautifully"], "0.9 6.8 5.3": ["distributions"], "0.5 6.4 -5.7": ["inspirational"], "3.4 14.8 2.4": ["admire"], "6.0 -8.0 9.0": ["awarding"], "17.3 7.1 -0.4": ["faulty"], "-6.1 11.9 11.4": ["pupil"], "4.4 -0.3 10.9": ["mills"], "14.0 25.4 5.5": ["stronghold"], "2.5 5.2 3.7": ["relaxing"], "7.4 8.6 11.6": ["gently"], "11.0 -1.1 5.8": ["promoter"], "12.3 4.2 12.5": ["flock"], "-0.5 27.7 7.2": ["generals"], "9.4 6.2 -3.1": ["unparalleled"], "4.2 15.4 12.0": ["tumors"], "10.4 8.8 6.9": ["pairing"], "5.2 11.3 8.8": ["wired"], "-3.0 -1.0 3.4": ["directs"], "-2.4 3.1 -1.1": ["psychologist"], "1.7 9.3 4.1": ["undermined"], "4.4 5.7 -7.0": ["negligence"], "10.9 12.3 29.3": ["apple"], "21.1 7.6 11.4": ["spectacle"], "7.3 14.0 8.0": ["hug"], "5.4 21.3 3.0": ["socialist"], "17.5 6.4 17.2": ["homemade"], "10.9 6.6 1.6": ["stadiums"], "-0.1 11.5 10.2": ["crease"], "-0.6 -2.0 1.8": ["accreditation"], "1.8 8.7 5.4": ["benchmarks"], "2.7 5.7 9.2": ["daytime"], "-4.4 -2.1 1.6": ["moderated"], "-1.2 5.6 1.1": ["stressing"], "13.1 6.0 1.2": ["downgrade"], "-3.8 -0.6 -3.0": ["ratified"], "8.2 11.9 2.3": ["particles"], "1.5 9.8 8.6": ["landowners"], "2.4 4.6 -3.5": ["reminding"], "-6.8 3.1 6.4": ["sedan"], "2.5 -0.7 5.7": ["inserted"], "8.9 2.4 1.9": ["underscored"], "8.5 4.1 3.5": ["hugely"], "52.1 2.2 -2.2": ["conglomerate"], "-2.0 7.1 18.3": ["methamphetamine"], "9.9 14.3 20.4": ["fog"], "2.6 1.9 4.3": ["debating"], "-4.6 12.9 11.2": ["bowler"], "17.6 8.7 10.0": ["slides"], "2.8 5.2 15.8": ["gardening"], "-8.5 2.8 0.1": ["deserving"], "7.4 4.4 10.0": ["hourly"], "3.5 11.0 -0.0": ["admired"], "16.1 7.4 10.2": ["rocky"], "-6.3 5.0 1.5": ["batted"], "3.8 13.3 12.0": ["wilderness"], "-0.4 1.3 10.7": ["lasts"], "-2.7 23.4 2.5": ["patrolling"], "1.4 7.0 22.4": ["wetlands"], "18.5 12.4 4.2": ["dimensional"], "30.5 19.6 12.9": ["robots"], "-6.5 4.8 7.6": ["decreases"], "3.3 5.7 1.2": ["grueling"], "7.3 -4.0 6.0": ["paving"], "-2.1 11.9 0.1": ["coincidence"], "-2.3 8.9 6.7": ["substances"], "4.2 0.3 5.0": ["exhibitions"], "10.1 27.0 16.7": ["prey"], "4.3 3.1 13.4": ["jobless"], "0.5 11.7 9.1": ["determines"], "9.7 6.5 -3.9": ["raping"], "6.1 -1.2 1.8": ["collects"], "3.2 6.2 4.1": ["fade"], "2.0 20.4 -1.0": ["altitude"], "12.0 19.5 16.8": ["cave"], "11.3 4.4 2.6": ["sway"], "0.9 8.9 5.9": ["lads"], "5.1 4.0 6.5": ["outlines"], "16.4 -5.0 2.8": ["spate"], "1.4 -0.2 -0.1": ["transitional"], "13.3 15.1 5.0": ["lonely"], "13.4 14.3 13.0": ["ax"], "17.3 19.7 4.2": ["symbols"], "16.5 5.6 -1.2": ["scanning"], "3.9 5.5 -3.0": ["updating"], "-3.9 10.2 5.6": ["deprived"], "-1.1 10.8 13.6": ["contingency"], "-3.9 3.4 3.8": ["megawatts"], "6.0 6.9 3.9": ["complementary"], "3.8 9.6 6.4": ["homecoming"], "11.1 0.9 -2.7": ["snatched"], "12.4 -2.0 1.6": ["brighter"], "-2.0 -2.6 4.8": ["convened"], "2.5 8.9 14.2": ["warmer"], "3.9 0.9 13.5": ["landscaping"], "-1.0 4.3 13.8": ["leadoff"], "-9.1 15.1 12.9": ["narcotics"], "0.7 8.0 25.6": ["cuisine"], "-2.5 3.4 5.5": ["disciplines"], "2.7 7.1 5.6": ["norms"], "8.9 14.6 7.1": ["weary"], "2.8 18.5 3.4": ["sneak"], "8.8 3.9 13.4": ["skid"], "4.9 10.4 1.9": ["thunderstorms"], "12.3 3.0 9.9": ["composite"], "1.7 15.5 1.1": ["distances"], "1.2 4.6 -3.9": ["informing"], "4.4 -2.3 2.1": ["concluding"], "1.3 3.8 -4.9": ["circulated"], "2.5 12.0 0.3": ["systematic"], "0.6 13.7 -2.5": ["distinguish"], "-1.8 3.7 9.0": ["cyclists"], "9.8 -0.3 4.7": ["simpler"], "-0.1 11.8 7.6": ["theories"], "3.9 12.4 5.9": ["wildfire"], "15.7 4.5 17.9": ["staple"], "-4.3 8.0 7.7": ["thereafter"], "14.9 2.8 13.9": ["anchored"], "-6.2 9.8 1.6": ["motivate"], "12.8 9.9 8.0": ["stunt"], "8.8 -1.5 0.3": ["racked"], "9.8 4.2 4.5": ["rash"], "13.6 15.3 10.4": ["greed"], "-9.5 3.2 -6.8": ["professionalism"], "-0.4 6.7 9.2": ["onset"], "7.8 11.7 6.3": ["roaming"], "8.4 17.8 5.7": ["passive"], "1.2 26.7 3.6": ["perpetrators"], "7.0 4.1 -0.5": ["rang"], "9.1 14.2 9.1": ["awhile"], "3.9 7.0 10.7": ["homestand"], "-4.9 11.5 7.8": ["deportation"], "11.8 4.3 9.6": ["clout", "gawkers"], "6.6 4.8 0.5": ["relegated"], "6.7 8.8 5.4": ["bored"], "1.5 5.5 -1.0": ["relevance"], "8.8 11.6 20.0": ["picnic"], "0.4 11.3 -5.5": ["routed"], "24.6 5.2 8.2": ["snapping"], "13.3 21.3 5.4": ["hackers"], "18.7 35.7 19.1": ["alien"], "1.8 1.8 4.4": ["owing"], "-2.1 7.4 -4.1": ["advocating"], "9.6 12.9 9.2": ["figuring", "catharses"], "4.9 22.0 4.5": ["rebellion"], "19.2 1.6 7.8": ["inflated"], "4.8 5.4 8.0": ["indices"], "7.7 12.4 0.3": ["chanting"], "-0.7 3.4 -4.6": ["capacities"], "8.1 4.1 2.6": ["surpass"], "-4.8 -3.3 2.2": ["revoked"], "-1.2 5.5 12.2": ["bred"], "10.9 6.1 7.3": ["fiery"], "-5.3 7.3 0.6": ["transcript"], "-8.5 18.9 6.4": ["religions"], "4.1 -7.0 2.9": ["refunds"], "7.1 6.1 6.4": ["grader"], "-1.0 2.7 4.4": ["worsened"], "11.1 10.6 13.8": ["whip"], "6.6 -3.5 -0.7": ["coincide"], "-6.8 8.7 -1.4": ["stressful"], "4.9 4.0 3.0": ["underwear"], "4.4 10.4 5.9": ["rooted"], "0.8 21.2 9.5": ["modes"], "5.9 15.0 5.3": ["vows"], "9.2 18.9 7.9": ["obstruction"], "4.4 7.1 7.4": ["hood"], "-5.4 30.7 2.3": ["faction"], "-2.0 2.6 3.9": ["belts", "urethra"], "-2.0 6.5 1.6": ["adamant"], "6.2 12.2 29.2": ["apples"], "16.9 10.1 4.5": ["astonishing"], "6.4 0.5 12.4": ["spoiled"], "11.8 -1.4 -2.7": ["showcasing"], "-6.7 7.5 11.3": ["caregivers"], "0.5 12.0 -3.2": ["provocative"], "4.7 14.3 9.2": ["colonial"], "7.0 9.3 12.5": ["scrum", "crunches"], "7.5 6.8 5.6": ["diversify"], "-1.4 2.0 10.1": ["dementia"], "1.7 3.0 8.8": ["descriptions"], "4.3 30.5 5.6": ["militias"], "-2.8 10.6 0.4": ["inquest"], "2.3 10.4 1.3": ["escort"], "17.3 2.2 2.8": ["runaway"], "0.9 3.0 3.2": ["deadlines"], "14.4 13.2 10.9": ["glorious"], "-5.4 -0.5 -0.9": ["aspiring"], "7.8 5.8 9.5": ["freeway"], "11.3 11.5 7.9": ["unfairly"], "13.0 -4.6 6.2": ["coupon"], "14.1 19.0 1.7": ["barrage"], "8.9 -0.9 0.6": ["competes"], "4.9 0.4 2.4": ["fared"], "12.6 22.0 17.6": ["ass"], "12.8 15.2 6.1": ["gadgets"], "8.7 9.5 13.5": ["abundant"], "13.8 14.9 5.0": ["blitz"], "-1.7 -0.6 -6.4": ["audits"], "10.5 22.0 9.1": ["useless"], "8.8 4.7 9.2": ["nailed"], "8.3 -6.7 0.8": ["oversaw"], "13.1 15.9 14.3": ["robber"], "-0.6 2.8 23.5": ["culinary"], "8.6 15.0 4.3": ["perceptions"], "14.6 4.1 6.3": ["directory"], "-2.2 1.1 1.2": ["workflow"], "9.1 18.3 1.7": ["alliances"], "1.2 -2.7 -0.0": ["safeguards"], "1.3 23.9 2.3": ["injustice"], "2.5 -1.3 5.9": ["affluent"], "8.6 3.3 0.6": ["creators"], "14.3 12.2 1.8": ["obscure"], "1.0 6.2 8.1": ["landlords"], "-6.8 -2.6 -1.1": ["forwarded"], "-0.7 3.4 3.3": ["deteriorated"], "4.3 -1.0 -3.3": ["conceived"], "5.1 -3.7 2.9": ["examines"], "12.1 5.7 13.5": ["dash"], "20.0 15.3 9.5": ["staring"], "6.4 -6.1 -0.1": ["irregularities"], "8.6 45.7 4.7": ["foe"], "6.4 3.5 11.0": ["silicon"], "12.8 13.0 7.0": ["atomic"], "18.8 4.6 0.9": ["erected"], "9.5 6.2 0.9": ["commemorate"], "16.0 10.6 10.5": ["canvas"], "-3.2 8.6 -1.6": ["outspoken"], "0.2 0.1 -1.7": ["renovated"], "4.1 13.3 11.7": ["toes"], "12.6 4.4 7.7": ["footing"], "19.4 -0.9 8.4": ["booths"], "13.2 28.2 5.5": ["dictator"], "4.9 3.4 6.2": ["upfront"], "5.6 5.4 9.8": ["jerseys"], "8.2 1.8 14.1": ["groceries"], "0.1 12.3 2.6": ["sadness"], "-5.9 6.3 -1.9": ["nominate"], "3.8 9.2 8.0": ["socks"], "-0.3 15.4 5.8": ["hesitate"], "5.5 7.9 16.3": ["creek"], "0.3 0.9 6.9": ["restriction"], "1.3 16.1 11.2": ["seldom"], "-5.2 7.5 -0.6": ["knowledgeable"], "11.9 12.0 40.3": ["shark"], "15.9 11.9 9.5": ["masks"], "0.9 14.6 3.5": ["bloodshed"], "1.7 19.8 3.1": ["prejudice"], "6.1 15.5 7.4": ["unstable"], "1.5 3.9 7.1": ["breakout"], "20.1 25.1 10.8": ["jungle"], "7.0 11.2 -1.4": ["proclaimed"], "16.7 3.1 8.3": ["splash"], "9.5 9.2 5.2": ["forecasters"], "3.0 6.5 6.3": ["voltage"], "1.9 2.0 12.1": ["steroid"], "7.9 3.5 2.3": ["noticeable"], "15.8 19.1 4.0": ["backwards"], "9.4 3.0 0.6": ["continents"], "13.9 3.6 -7.6": ["renamed"], "9.2 18.2 7.7": ["bury"], "5.0 2.3 9.9": ["dances"], "-2.4 12.1 5.5": ["outset"], "0.4 -0.8 11.5": ["nutritional"], "22.7 1.8 1.5": ["pharmaceuticals"], "7.3 14.8 0.3": ["internally"], "-2.4 4.6 2.6": ["refinance"], "-4.0 0.9 3.3": ["audition", "hydroxylase"], "-3.3 -0.0 9.4": ["lodging"], "7.1 9.7 7.0": ["possessing"], "6.2 7.7 5.2": ["brake"], "3.6 12.2 8.2": ["reluctance"], "-4.8 -1.6 0.9": ["counselors"], "12.2 1.7 3.5": ["hangs"], "25.1 14.8 7.6": ["icons"], "-0.6 12.6 13.3": ["waist"], "-1.6 4.6 2.5": ["paragraph"], "-0.6 8.4 7.8": ["concede"], "3.0 11.2 2.0": ["prayed"], "-1.0 13.0 -0.8": ["objection"], "5.2 0.5 -0.4": ["explores"], "23.0 3.2 8.7": ["sizable"], "13.7 18.2 10.8": ["dumb"], "16.5 7.3 12.8": ["piles"], "8.6 16.0 5.1": ["beam"], "3.2 13.0 -2.9": ["condemnation"], "3.4 12.0 5.9": ["junta"], "9.9 6.1 16.7": ["logs"], "11.9 -1.6 0.6": ["bolstered"], "11.5 1.7 -0.9": ["danced"], "0.7 1.8 0.7": ["repaid"], "3.8 15.1 9.0": ["sadly"], "12.8 0.3 2.7": ["tucked"], "4.6 8.0 6.6": ["fifty"], "6.4 12.0 6.3": ["boxer"], "-9.0 0.8 3.7": ["residences"], "2.0 -1.8 -6.0": ["lauded"], "5.3 8.1 2.2": ["downloading"], "-1.5 -2.5 1.3": ["disqualified"], "13.3 3.8 9.3": ["retiree"], "3.8 1.9 2.5": ["fringe"], "3.7 4.3 8.5": ["pharmacies"], "-1.7 9.9 5.1": ["putts"], "-0.7 2.1 1.3": ["implicated"], "-4.9 11.8 2.1": ["memoir"], "0.3 2.0 -2.3": ["enhances"], "5.0 9.5 30.7": ["honey"], "-10.7 15.6 4.0": ["homosexuality"], "5.9 -2.9 1.3": ["boutique"], "-2.0 5.7 -6.6": ["advocated"], "-0.2 9.5 12.3": ["comics"], "2.9 7.8 -2.3": ["explicit"], "10.7 10.6 13.3": ["lazy"], "-1.3 14.4 8.2": ["linebackers"], "3.5 15.3 5.6": ["desperation"], "12.5 4.1 7.3": ["fading"], "7.3 1.2 -2.7": ["impairment"], "8.7 -0.4 5.3": ["memorabilia"], "14.3 4.6 3.1": ["specially"], "-0.4 9.0 1.9": ["discomfort"], "2.7 21.2 3.4": ["fugitive"], "8.0 2.1 12.9": ["cups"], "-3.7 27.1 11.1": ["shooters"], "6.7 8.0 7.1": ["snaps"], "5.1 3.3 -0.5": ["underlined"], "26.9 3.2 7.3": ["telecoms"], "5.3 12.3 7.7": ["hobby"], "-0.7 10.6 3.9": ["sings"], "-4.5 9.0 1.8": ["confession"], "0.9 6.0 5.1": ["persist"], "6.5 12.9 6.5": ["emerges"], "0.0 0.4 -7.0": ["entertained"], "9.3 -1.1 -1.8": ["lured"], "-0.8 7.1 1.0": ["feasible"], "-4.8 12.6 4.9": ["arresting"], "11.7 7.7 10.9": ["stricken"], "9.9 0.2 -2.8": ["reaffirmed"], "15.6 3.0 6.5": ["reversing"], "11.6 11.5 18.5": ["cousins"], "3.6 21.7 6.3": ["peacekeepers"], "1.8 3.6 12.7": ["zinc"], "-0.7 13.5 3.1": ["sectional"], "0.5 8.1 5.8": ["pneumonia"], "6.9 28.0 10.0": ["maneuver"], "24.7 27.1 14.3": ["god"], "9.1 12.5 2.3": ["molecules"], "9.6 5.3 10.9": ["syndrome"], "1.0 23.4 9.3": ["ignorance"], "12.8 7.3 5.9": ["assemble"], "12.1 8.3 0.7": ["tearing"], "-6.8 13.3 7.4": ["impeachment"], "4.2 5.4 1.0": ["electronically"], "4.3 8.8 0.7": ["erase"], "4.7 17.7 6.6": ["obey"], "-4.8 11.3 7.8": ["texting"], "0.6 3.4 -0.6": ["provisional"], "5.6 4.6 3.9": ["restricting"], "15.7 19.7 10.1": ["thief"], "5.5 15.2 2.4": ["readily"], "6.8 6.4 15.0": ["oven"], "5.8 4.9 20.0": ["cocktail"], "-1.5 14.9 5.5": ["disadvantage"], "-7.2 7.8 -2.0": ["biography"], "7.0 9.9 15.7": ["ritual"], "12.6 -0.0 9.6": ["spree"], "13.5 -2.0 1.2": ["synthetic"], "4.1 -1.3 19.4": ["nursery"], "2.9 9.0 6.4": ["trek"], "8.6 7.0 0.2": ["filters"], "-0.3 16.7 9.5": ["reasoning"], "8.9 13.5 1.1": ["revolt"], "6.3 -0.4 -1.6": ["bundled"], "3.1 9.3 18.8": ["grill"], "11.6 0.3 4.3": ["boosts"], "1.9 7.2 3.9": ["lung"], "0.3 2.8 11.8": ["poorer"], "0.7 16.2 14.4": ["depleted"], "12.4 1.2 9.1": ["abruptly"], "6.9 -4.3 1.0": ["vouchers"], "-1.1 3.7 -8.3": ["congratulated"], "16.4 9.5 20.8": ["foam"], "9.7 10.7 8.2": ["avert"], "5.5 10.7 4.8": ["harmed"], "-0.2 6.5 6.8": ["pins"], "7.0 3.1 3.2": ["awaited"], "5.8 7.8 1.3": ["modernization"], "0.3 2.2 0.8": ["impasse"], "6.7 5.6 9.8": ["sped"], "5.3 12.4 20.1": ["inland"], "8.4 21.9 17.0": ["treasure"], "11.4 12.8 2.8": ["bend"], "0.4 3.0 -0.8": ["disclosures"], "6.9 15.6 7.9": ["weakest"], "1.6 4.3 4.2": ["caretaker"], "3.2 10.7 8.9": ["polite"], "18.5 1.0 17.4": ["carnival"], "7.0 12.0 10.6": ["rob"], "-1.7 7.1 2.5": ["inconvenience"], "0.8 8.9 5.1": ["departing"], "7.9 4.7 5.1": ["escalated"], "-1.8 7.3 4.3": ["bogeys"], "12.1 1.0 0.1": ["underscores"], "18.4 14.0 16.8": ["rats"], "10.7 14.8 1.2": ["conspiring"], "4.7 1.0 6.8": ["traction"], "2.0 5.1 0.5": ["ouster"], "6.9 12.3 2.3": ["ironic"], "11.9 6.3 4.3": ["torch"], "24.4 1.2 8.7": ["soar"], "4.5 6.9 5.3": ["procession"], "2.8 0.1 1.2": ["administer"], "4.8 -3.6 3.6": ["opting"], "6.9 6.9 7.9": ["scratched"], "5.3 9.4 7.4": ["fractured"], "16.4 1.8 16.4": ["plastics"], "0.7 12.5 14.3": ["outbreaks"], "-1.7 -2.5 12.1": ["preschool"], "20.5 7.9 5.5": ["rip"], "7.8 5.5 4.5": ["brawl"], "3.9 4.6 18.6": ["champagne"], "20.6 11.4 5.6": ["makeshift"], "17.8 2.4 0.0": ["propelled"], "7.9 27.4 2.1": ["brigade"], "8.0 4.8 -5.4": ["abusing"], "11.2 26.4 -9.3": ["bombed"], "-1.3 -4.0 7.9": ["supplements"], "7.0 25.3 2.8": ["confronting"], "10.4 0.4 7.9": ["crowned"], "-2.5 2.9 2.7": ["compensated"], "0.3 5.4 10.6": ["mayors"], "4.4 20.8 -2.4": ["patriotic"], "1.1 1.1 1.0": ["terminate"], "5.3 14.3 4.2": ["implies"], "0.6 -0.1 16.8": ["resumption"], "13.9 0.1 3.5": ["makeover"], "2.1 7.3 2.1": ["vein"], "3.7 10.7 4.9": ["intraday"], "27.4 10.7 23.2": ["lion"], "15.7 9.7 10.8": ["hey"], "-4.0 6.3 0.4": ["altercation"], "0.1 10.0 8.0": ["dealerships"], "-1.9 2.2 0.7": ["mins"], "-2.2 21.2 2.2": ["motives"], "15.3 -2.1 3.4": ["bundle"], "12.9 1.6 2.9": ["bogus"], "8.6 9.9 18.4": ["litter"], "11.0 19.8 34.6": ["seas"], "1.8 14.3 11.2": ["despair"], "9.2 5.6 2.8": ["outcry"], "-1.2 2.7 6.0": ["yarder"], "10.0 2.7 3.4": ["illustrates"], "18.5 20.9 11.2": ["capitalism"], "7.8 5.9 5.6": ["sourcing"], "5.6 0.9 8.0": ["bumped"], "-4.8 12.3 2.5": ["inexperienced"], "14.6 16.8 1.5": ["frontier"], "3.7 4.4 2.2": ["fifteen"], "10.4 8.5 18.0": ["dwindling"], "10.2 5.0 5.7": ["illustrated"], "2.8 -1.6 8.3": ["deposited"], "-2.0 8.4 4.8": ["diary"], "9.6 19.5 9.0": ["robbers"], "10.8 8.1 20.4": ["rigs"], "10.9 9.1 6.4": ["stabilizing"], "2.7 12.4 1.2": ["explicitly"], "1.2 2.8 1.8": ["fumbled"], "2.4 8.9 2.0": ["prospectus"], "7.6 12.0 9.6": ["sting"], "8.6 -1.7 4.1": ["standardized"], "12.4 4.7 2.6": ["reap"], "10.9 14.4 7.5": ["manipulation"], "0.2 4.8 10.8": ["gatherings"], "10.9 5.6 13.7": ["slips", "glassmakers"], "-0.2 7.0 2.3": ["baggage"], "11.9 15.1 17.5": ["sunk"], "4.0 3.6 7.1": ["cheek"], "5.5 12.0 6.4": ["fences"], "-2.5 5.1 3.9": ["arraignment"], "7.5 -2.9 2.6": ["embarked"], "8.2 22.4 -2.0": ["spying"], "8.6 -1.6 11.9": ["kilograms"], "9.0 13.1 8.2": ["knockout"], "-4.4 3.3 -2.7": ["emphasizes"], "0.4 0.2 4.0": ["briefs"], "3.6 6.3 11.1": ["jockey"], "11.2 0.2 -0.5": ["regulating"], "5.4 12.8 1.6": ["hallway"], "10.2 -2.6 3.0": ["inject"], "6.0 12.2 6.1": ["gentleman"], "19.6 12.9 2.0": ["cartel"], "0.2 8.6 7.8": ["conserve"], "-1.5 3.9 10.0": ["airs"], "9.6 1.0 10.6": ["richer"], "-8.3 12.4 -1.0": ["prosecuting"], "9.2 10.6 16.4": ["porch"], "11.2 15.5 14.1": ["icy"], "-3.4 5.8 48.5": ["fisheries"], "-4.7 11.2 5.0": ["tiebreaker"], "10.5 11.4 7.8": ["pundits"], "2.7 0.0 0.0": ["scalable"], "-0.7 9.0 5.3": ["seriousness"], "-9.9 -1.1 7.2": ["vacations"], "2.9 9.5 17.5": ["variation"], "1.2 3.3 2.3": ["pleas"], "3.4 16.0 1.1": ["ashamed"], "5.2 5.8 9.0": ["rubbish"], "5.4 5.2 4.7": ["clinching"], "19.6 11.2 8.5": ["tilt"], "12.8 28.6 0.5": ["invaded"], "9.3 9.6 5.4": ["elevator"], "3.1 9.9 7.5": ["roofs"], "5.5 6.9 9.0": ["vet"], "5.8 -3.9 9.6": ["mg"], "-1.7 7.6 1.9": ["disturbed"], "-4.1 1.7 2.8": ["undecided"], "-4.6 9.0 6.8": ["depart"], "14.6 28.1 4.3": ["civilization"], "-3.7 10.0 3.0": ["interoperability"], "5.0 5.9 4.8": ["plaque"], "0.3 5.8 0.5": ["emphasizing"], "2.4 -5.9 3.2": ["subscriptions"], "4.9 7.8 8.1": ["tempted"], "8.4 2.8 3.8": ["bribes"], "12.9 -2.3 11.4": ["payout"], "8.5 6.8 7.7": ["prosperous"], "13.4 13.3 7.5": ["exporting"], "11.5 1.5 -1.6": ["teaming"], "0.4 8.8 10.9": ["refugee"], "11.8 8.6 6.4": ["counters"], "9.3 -4.6 -3.0": ["showcased"], "-7.8 -1.7 -0.3": ["waivers"], "-1.5 16.4 5.4": ["sectarian"], "4.2 15.9 8.7": ["geography"], "2.7 15.6 6.5": ["earthquakes"], "1.2 6.7 2.9": ["tremendously"], "11.1 15.2 7.5": ["censorship"], "-1.4 7.9 14.1": ["farmland"], "10.3 11.3 3.7": ["fairway"], "5.4 1.7 5.0": ["biofuels"], "9.0 0.5 2.7": ["severance"], "4.1 4.2 4.1": ["stature"], "-5.1 11.2 2.3": ["sexuality"], "4.9 3.2 2.0": ["vault"], "4.9 15.6 7.1": ["affection"], "7.5 16.9 4.9": ["frightened"], "11.3 -6.0 1.3": ["suites"], "5.6 -2.6 9.7": ["stemmed"], "-0.3 6.3 3.3": ["feud"], "-0.0 3.3 0.7": ["renting"], "19.6 11.1 9.5": ["legends"], "4.4 15.0 3.2": ["sustaining"], "6.7 11.6 4.0": ["blunt", "sparkless"], "15.5 14.3 27.1": ["tiger"], "2.5 10.3 -6.2": ["misuse"], "1.8 5.4 4.5": ["hears"], "2.7 20.3 9.8": ["fearful"], "-4.7 8.1 0.5": ["critically"], "-0.1 15.2 6.5": ["strikers"], "4.8 15.3 -2.2": ["intimidated"], "-2.9 10.0 4.2": ["judgments"], "14.4 -1.7 -1.3": ["modeled"], "4.6 7.9 8.0": ["drowning"], "5.0 9.9 4.7": ["reclaim"], "5.0 4.2 8.1": ["quartet"], "4.0 25.7 10.4": ["sin"], "10.7 4.8 22.1": ["menus"], "11.6 -3.3 -0.8": ["lobbied"], "3.9 3.7 0.1": ["unused"], "-2.3 10.9 2.5": ["discouraged"], "9.6 -6.6 2.1": ["spans"], "15.7 11.7 1.3": ["dimensions"], "9.9 7.5 8.9": ["perennial"], "12.7 27.6 24.1": ["insects"], "-5.6 7.6 2.7": ["perspectives"], "-2.3 2.1 15.3": ["cannabis"], "3.2 -7.0 4.3": ["sorted"], "0.5 16.8 8.6": ["escalation"], "13.3 20.9 2.9": ["intimidating"], "13.8 16.7 7.1": ["obsession"], "15.7 4.5 4.2": ["popping"], "-2.8 8.1 1.9": ["interventions"], "7.2 6.3 4.5": ["tabloid"], "11.6 5.9 21.7": ["snack"], "3.3 7.0 6.4": ["recovers"], "7.7 9.6 2.1": ["succeeds"], "-8.2 11.9 8.2": ["mineralization"], "6.6 6.7 5.7": ["candles"], "15.9 7.1 1.4": ["harness"], "3.7 5.9 -3.4": ["openness"], "9.4 5.6 5.8": ["fraternity"], "-1.3 8.5 4.8": ["offended"], "-5.7 7.7 -5.9": ["inflammatory"], "3.3 0.8 -1.0": ["printers"], "0.6 29.1 12.8": ["gameplay"], "6.2 12.7 6.7": ["unreasonable"], "7.5 20.0 7.8": ["utterly"], "-3.5 -3.5 3.8": ["allowances"], "13.2 13.4 16.8": ["deepening"], "3.0 8.0 12.4": ["dams"], "0.2 9.2 4.7": ["compelled"], "2.1 16.8 4.6": ["tornadoes"], "0.0 -1.3 -0.5": ["developmental"], "5.0 3.7 -4.4": ["circulating"], "11.4 1.4 13.6": ["scales"], "3.0 18.1 7.1": ["wildfires"], "1.9 6.9 12.8": ["fours"], "10.1 6.2 6.3": ["rests"], "7.2 -1.6 5.2": ["geared"], "1.3 11.4 3.2": ["delete"], "6.0 -3.2 4.9": ["exhibitors"], "8.9 9.6 6.4": ["provoked"], "10.2 10.3 1.2": ["separating"], "6.9 13.9 4.7": ["screamed"], "6.4 6.7 5.3": ["lag"], "0.3 4.8 3.2": ["adequacy"], "3.0 5.0 8.6": ["bachelor"], "-6.4 -1.5 1.0": ["vacancies"], "-5.2 4.4 3.7": ["recess"], "7.8 7.9 16.5": ["customary"], "9.2 18.3 6.5": ["punching"], "1.9 19.9 7.6": ["observer"], "-2.9 2.0 -0.0": ["exemptions"], "3.0 0.3 -2.4": ["authenticity"], "18.2 5.4 0.8": ["cheapest"], "4.4 11.4 3.6": ["videotape"], "-2.2 10.0 5.1": ["observing"], "-0.6 -0.0 -2.2": ["validation"], "-4.2 -4.0 0.6": ["adjourned"], "2.5 21.7 4.0": ["dictatorship"], "5.5 5.6 6.5": ["mailing"], "-2.9 6.2 2.4": ["surgeons"], "20.9 12.0 -1.6": ["invention"], "0.5 9.8 3.4": ["biased", "racemic"], "9.9 -1.8 0.6": ["outlining"], "12.2 11.1 2.6": ["automobiles"], "7.8 13.9 12.8": ["chess"], "4.1 -3.4 7.2": ["stricter"], "-1.7 7.5 0.4": ["interpret"], "5.9 4.4 10.7": ["sour"], "7.7 7.7 9.9": ["towel"], "6.4 10.6 0.3": ["intuitive"], "2.2 15.7 -1.1": ["accessory"], "-0.5 8.5 17.9": ["tasting"], "4.3 11.3 6.2": ["spine"], "4.8 5.6 6.4": ["muster"], "4.5 10.7 1.7": ["assaulting"], "8.6 12.5 0.9": ["gestures"], "-1.7 18.3 0.4": ["leftist"], "9.6 7.1 6.9": ["curtain"], "9.9 2.4 4.5": ["derail"], "8.2 13.3 10.4": ["perfection"], "4.9 13.1 12.9": ["greenback"], "2.2 4.4 33.5": ["pepper"], "4.9 7.5 12.5": ["pubs"], "9.5 20.6 11.8": ["sunlight"], "-1.6 19.8 5.3": ["challengers"], "10.0 5.5 3.7": ["dubious"], "6.6 6.5 12.7": ["subprime"], "-5.4 8.7 -4.0": ["texts"], "7.6 13.7 2.9": ["overcoming"], "-9.7 -3.1 7.5": ["workload"], "-5.5 3.4 4.3": ["expiration"], "10.0 16.3 3.4": ["republic"], "7.2 13.0 4.2": ["repairing"], "8.1 8.6 9.1": ["witnessing"], "-1.6 3.2 9.9": ["parenting"], "0.9 3.8 20.4": ["boil"], "18.8 -2.2 -0.5": ["revamp"], "8.4 4.8 0.9": ["convergence"], "-1.8 3.1 4.8": ["textbooks"], "-7.1 2.5 7.8": ["warranted"], "13.4 28.9 2.9": ["invade"], "8.0 12.1 5.6": ["expressions"], "8.1 11.5 1.8": ["tasked"], "1.5 11.5 1.1": ["endurance"], "1.4 5.8 11.4": ["lockout"], "8.7 2.9 5.0": ["widen"], "-2.3 14.9 7.4": ["matchups"], "3.0 1.9 4.3": ["embark"], "5.0 3.2 12.3": ["ballet"], "4.6 15.3 3.3": ["shout"], "-3.6 14.6 8.6": ["poem"], "12.9 15.4 -0.3": ["hid"], "-1.2 2.2 0.7": ["educator"], "20.3 17.2 8.0": ["domination"], "6.5 5.2 -4.2": ["applaud"], "10.6 8.5 18.7": ["bricks"], "-5.9 11.4 21.9": ["meth"], "-4.7 13.8 19.7": ["ore"], "4.5 9.6 2.5": ["align"], "27.8 -3.4 9.3": ["burgeoning"], "3.0 1.2 3.7": ["valuations"], "2.2 8.7 5.9": ["obliged"], "5.4 4.3 2.3": ["decree"], "18.1 -3.5 4.6": ["eyeing"], "4.5 9.4 6.2": ["waits"], "12.0 20.1 8.3": ["equals"], "1.2 3.0 6.9": ["chassis"], "18.5 13.6 7.6": ["explode"], "3.7 3.8 4.4": ["replacements"], "2.7 0.8 21.8": ["flats"], "13.1 4.0 7.1": ["descended"], "-4.0 13.1 6.8": ["constituencies"], "9.4 19.0 13.9": ["containment"], "-4.3 15.2 10.9": ["incumbents"], "7.1 5.0 -1.1": ["ringing"], "12.2 4.0 1.8": ["televisions"], "-1.2 22.4 0.3": ["accusation"], "8.3 5.1 8.5": ["horsepower"], "10.2 3.5 8.3": ["frantic"], "9.1 0.0 4.8": ["modestly"], "7.6 1.3 13.1": ["earnest"], "9.9 8.5 3.3": ["proponents"], "-8.6 3.5 8.5": ["sophomores"], "-1.5 4.6 1.5": ["deduction"], "-1.2 7.9 7.9": ["jails"], "6.0 -0.1 6.7": ["cutbacks"], "18.1 3.8 10.0": ["handsome"], "-3.1 7.7 15.5": ["beers"], "-0.5 -3.4 5.6": ["diploma"], "-2.6 28.9 2.6": ["doctrine"], "5.2 9.2 0.9": ["routing"], "10.0 10.3 8.5": ["periodically"], "14.5 10.1 6.0": ["cornerstone"], "0.5 -5.0 -2.1": ["pertaining"], "11.0 10.9 1.9": ["resilience"], "2.2 9.0 -1.0": ["publicist"], "9.1 8.9 12.3": ["dull"], "1.5 -2.8 -2.5": ["validity"], "14.3 13.7 14.8": ["depths"], "-5.4 -2.0 3.5": ["signings"], "5.3 14.4 8.6": ["shrine"], "12.4 15.9 2.9": ["marching"], "4.9 9.9 2.3": ["predecessors"], "-3.7 7.2 2.7": ["bruises"], "14.1 23.4 3.5": ["onslaught"], "-0.6 4.6 1.2": ["intermission"], "1.1 4.1 12.0": ["redistribution"], "12.8 1.2 -0.1": ["resurgence"], "-0.7 6.6 8.8": ["wrestler"], "5.5 -1.5 -1.4": ["devote"], "13.5 7.6 8.7": ["roadside"], "-5.0 2.9 12.5": ["arrivals"], "6.9 33.0 -2.3": ["bombers"], "4.7 12.2 10.2": ["helmets"], "15.9 15.0 10.1": ["flame"], "14.9 13.5 4.0": ["depicted"], "11.0 22.1 9.6": ["rulers"], "27.1 17.3 26.2": ["snake"], "5.1 6.7 19.6": ["herd"], "-4.7 11.6 15.6": ["influenza"], "6.4 10.9 6.1": ["retract"], "11.2 2.5 8.5": ["tipping"], "9.6 -1.8 4.2": ["promoters"], "7.7 29.9 4.3": ["arsenal"], "8.8 7.9 9.3": ["onstage"], "0.9 5.4 2.8": ["jeopardize"], "-2.9 16.1 7.8": ["manpower"], "5.1 15.9 10.9": ["spells"], "-1.5 4.4 -2.1": ["vacated"], "8.6 -0.3 9.2": ["lodge"], "2.8 14.1 -0.7": ["shortcomings"], "8.6 9.0 3.6": ["wrongly"], "7.0 -5.5 -3.7": ["debuts"], "3.2 16.1 7.0": ["rationale"], "4.7 0.4 5.0": ["stabilized"], "5.1 5.9 9.8": ["compounded"], "4.4 7.4 9.3": ["cruising"], "-1.1 6.2 18.7": ["nutrients"], "-0.6 5.5 7.1": ["footwear"], "8.1 14.6 9.1": ["buildup"], "5.1 3.3 6.0": ["dentist"], "2.2 12.6 6.3": ["joking"], "4.0 6.6 8.6": ["markers"], "8.0 14.0 11.2": ["antenna"], "-2.6 6.2 1.4": ["substantive"], "-2.5 21.9 -3.0": ["courageous"], "2.8 10.8 10.6": ["roommate"], "8.8 18.9 6.6": ["terrified"], "8.9 8.4 8.6": ["mediocre"], "-1.0 8.6 1.9": ["taxed"], "8.0 9.7 10.4": ["consoles"], "12.7 4.4 7.3": ["clad"], "2.8 17.7 2.0": ["mosques"], "-7.8 -0.7 -1.2": ["clarified"], "10.4 13.7 2.2": ["knowingly"], "10.7 4.7 3.3": ["vigorous"], "10.8 12.0 28.7": ["coastline"], "13.0 17.2 12.0": ["inhabitants"], "5.0 16.3 2.3": ["unfamiliar"], "4.0 3.7 0.9": ["fanned"], "0.2 4.2 -3.4": ["respiratory"], "2.6 6.4 7.9": ["exclusion"], "2.4 6.5 4.2": ["banged"], "10.5 10.0 6.3": ["viral"], "1.6 1.1 0.2": ["milestones"], "3.7 10.4 3.2": ["humidity"], "4.7 14.3 2.8": ["render"], "5.4 15.4 3.7": ["pinpoint"], "16.2 12.0 3.6": ["abandoning"], "4.1 8.2 5.9": ["warmth"], "15.1 2.4 7.7": ["shrugged"], "11.4 6.9 9.4": ["stirring"], "9.6 6.9 8.6": ["tightly"], "2.0 10.4 7.3": ["offending"], "6.8 18.9 0.0": ["aiding"], "14.4 12.4 5.4": ["borne"], "2.4 17.2 7.8": ["volley"], "12.9 17.2 2.0": ["unlock"], "8.0 20.5 8.1": ["foolish"], "7.1 1.1 6.2": ["presenter"], "7.2 14.7 4.9": ["flush"], "-0.1 -0.4 8.9": ["shortened"], "8.5 32.2 5.9": ["ambush"], "9.5 0.8 -0.8": ["turbulent"], "10.8 26.0 9.0": ["buddies"], "9.3 10.9 -1.5": ["fictional"], "7.6 5.3 9.2": ["softer"], "6.5 3.7 3.0": ["counterfeit"], "14.4 12.2 -3.0": ["hijacked"], "2.4 1.6 6.2": ["sterling"], "7.5 13.7 45.3": ["whales"], "1.3 21.0 3.3": ["adversity"], "12.4 15.8 3.2": ["static"], "10.3 5.1 2.6": ["addicted"], "7.6 7.2 5.2": ["pulse"], "1.3 12.2 9.5": ["lefty"], "8.0 20.7 7.8": ["deflation"], "8.5 17.3 8.7": ["fist"], "1.8 17.5 3.2": ["undermining"], "-1.8 6.8 12.4": ["swimmer"], "-0.5 7.5 6.5": ["stalemate"], "11.6 4.4 1.3": ["outperform"], "7.6 3.4 12.3": ["strings"], "12.5 27.5 10.2": ["poison"], "18.4 4.0 6.0": ["centric"], "23.2 0.9 8.9": ["circular"], "5.0 12.5 3.8": ["mathematics"], "5.7 -0.1 -0.4": ["integrates"], "9.7 -0.2 12.9": ["lid"], "6.5 14.4 4.5": ["haunted"], "9.3 5.0 19.2": ["scoop"], "3.4 2.1 0.6": ["amassed"], "7.3 6.7 -1.2": ["synergies"], "16.7 0.3 7.4": ["upwards"], "-0.2 18.6 -0.6": ["divisive"], "-1.0 -2.9 4.2": ["budgeted"], "21.0 14.6 13.3": ["crippled"], "1.5 4.6 0.1": ["ambassadors"], "15.2 1.9 5.8": ["bailed"], "9.9 4.9 -0.8": ["lashed"], "4.9 8.0 9.8": ["flourish"], "-2.2 14.4 -1.9": ["guarded"], "1.9 24.3 3.0": ["overthrow"], "5.2 12.4 -2.9": ["consolidating"], "2.3 9.9 2.1": ["diminish"], "16.5 9.6 8.4": ["balloons"], "-0.6 4.8 6.4": ["worsen"], "3.2 4.6 0.0": ["queries"], "14.2 29.3 7.5": ["rogue"], "5.6 19.7 7.2": ["mistaken"], "9.7 4.5 3.6": ["rep"], "-1.9 21.1 1.4": ["ideals"], "9.2 18.8 8.6": ["insane"], "-4.2 8.5 9.0": ["lip"], "8.8 -1.2 -5.1": ["prominence"], "5.6 11.7 17.8": ["aforementioned"], "24.4 4.3 16.3": ["tumble"], "-10.0 3.1 -2.9": ["correspondence"], "14.5 9.3 10.7": ["brewing"], "22.7 8.6 5.3": ["collapsing"], "2.2 4.3 6.0": ["marginally"], "-0.7 2.8 5.5": ["ministerial"], "4.5 19.2 7.8": ["punishing"], "12.5 0.5 12.4": ["stalls"], "1.7 7.6 7.2": ["executions"], "0.6 4.1 13.9": ["wastewater"], "10.3 8.5 29.4": ["butterfly"], "0.5 4.6 14.8": ["jackets"], "6.2 6.2 12.5": ["laborers"], "19.5 1.7 -1.7": ["debacle"], "14.1 6.9 3.9": ["uniquely"], "13.0 14.8 2.6": ["handheld"], "6.3 0.3 6.6": ["polished"], "4.3 8.0 8.1": ["redistributed"], "8.8 0.6 9.7": ["pegged"], "-0.3 7.3 4.0": ["bedrooms"], "18.5 8.9 12.5": ["miner"], "17.1 10.7 -1.9": ["magnetic"], "15.2 1.1 10.8": ["attach"], "-6.1 2.1 2.2": ["referral"], "-4.9 2.5 9.6": ["regulars"], "8.4 24.7 29.8": ["submarine"], "10.9 11.9 4.9": ["manipulated"], "8.9 3.7 1.3": ["issuer"], "0.1 3.7 1.8": ["intervened"], "10.0 4.0 0.3": ["exited"], "5.5 15.5 -1.3": ["oust"], "4.0 12.7 -3.2": ["disruptive"], "1.2 -2.7 0.6": ["commencement"], "4.0 -0.5 12.0": ["parental"], "15.1 14.0 6.0": ["imagery"], "13.1 15.9 15.4": ["crap"], "9.7 15.6 6.6": ["ruins"], "2.7 9.6 -0.7": ["reacting"], "-0.8 9.6 13.6": ["elders"], "7.5 22.4 -2.1": ["guarding"], "2.8 4.5 1.4": ["constituted"], "3.7 1.8 12.0": ["bin"], "6.7 10.6 8.9": ["insistence"], "16.6 5.5 4.4": ["financials"], "18.3 1.0 14.6": ["bumper"], "1.9 2.9 5.8": ["insulin"], "-4.4 10.9 12.8": ["strikeout"], "4.1 -0.4 -0.2": ["youthful"], "0.6 -1.4 16.2": ["weddings"], "8.4 5.4 15.6": ["antique"], "-7.6 -4.0 -0.8": ["mentoring"], "8.0 18.8 6.5": ["motto"], "15.5 4.9 4.5": ["overlooking"], "4.2 14.7 4.5": ["alignment"], "0.1 5.5 -0.6": ["versatility"], "4.4 5.3 5.5": ["niece"], "-2.9 26.6 0.9": ["counterterrorism"], "4.4 5.3 22.2": ["gravel"], "6.0 11.7 -2.1": ["domestically"], "11.2 12.1 10.2": ["breeze"], "1.2 11.9 -3.9": ["vigilant"], "7.9 16.3 15.1": ["gut"], "13.2 10.1 0.9": ["constructing"], "4.3 12.1 8.7": ["acid"], "10.4 -6.4 6.6": ["auctioned"], "21.4 7.1 12.8": ["plunging"], "5.8 10.1 -1.6": ["systemic"], "-2.8 7.1 -3.6": ["analytical"], "15.8 11.0 5.2": ["rotating"], "8.1 13.9 7.7": ["declares"], "3.9 6.3 0.2": ["evidenced"], "5.2 12.4 7.9": ["balcony"], "10.9 6.0 7.0": ["cartoons"], "6.8 6.0 7.0": ["login"], "-1.7 13.7 -3.9": ["criticisms"], "18.7 -1.7 2.4": ["buoyed"], "-0.5 5.1 11.3": ["thigh"], "13.8 9.1 2.6": ["width"], "11.2 8.4 17.1": ["sunset"], "3.4 6.8 13.7": ["rupee"], "-0.7 -0.8 6.2": ["instituted"], "11.6 8.7 10.3": ["wrecked"], "-0.5 8.2 4.3": ["contemplated"], "4.2 13.1 15.6": ["knives"], "6.8 22.1 3.8": ["daring"], "13.9 12.3 4.0": ["mistakenly"], "13.0 13.7 4.0": ["multitude"], "18.4 14.6 9.9": ["swallow"], "2.6 6.5 -2.5": ["mentions"], "1.2 5.9 -4.1": ["condolences"], "-2.8 2.7 5.5": ["hesitant"], "1.3 4.3 4.6": ["entrepreneurial"], "4.5 12.6 5.4": ["beneficiary"], "8.7 14.4 2.6": ["illicit"], "6.9 10.0 11.5": ["cloth"], "4.4 14.1 10.5": ["meaningless"], "9.4 2.9 13.1": ["ripe"], "-4.3 6.2 8.3": ["lamented"], "3.1 12.3 9.8": ["tankers"], "11.5 6.3 8.2": ["jammed"], "15.3 28.2 15.4": ["devil"], "8.2 6.1 17.5": ["weighted"], "7.2 21.5 6.5": ["nuisance"], "-3.3 -3.4 8.6": ["suspensions"], "10.3 11.8 3.2": ["rendering"], "4.4 11.5 3.0": ["offline"], "5.8 5.2 2.4": ["gunpoint"], "-1.1 4.5 0.9": ["reside"], "23.1 1.6 5.8": ["fledgling"], "3.4 2.6 10.5": ["insulation"], "11.7 12.3 23.9": ["feast"], "1.4 3.9 20.0": ["asphalt"], "18.2 4.6 4.1": ["sleek"], "6.1 1.3 35.1": ["pasta"], "9.4 20.7 5.2": ["escaping"], "30.4 6.7 6.2": ["beleaguered"], "6.2 20.5 10.9": ["slaves"], "-3.7 13.4 10.2": ["coping"], "28.5 2.3 11.8": ["shiny"], "3.4 22.8 5.3": ["grenade"], "10.5 27.7 -2.7": ["occupying"], "19.6 -2.0 11.1": ["spiked"], "2.4 6.6 8.4": ["midweek"], "7.9 6.0 11.8": ["peaks"], "7.0 5.8 3.9": ["simplicity"], "4.6 3.9 5.0": ["rethink"], "-2.3 -1.4 0.3": ["prepaid", "aggrevated"], "3.7 18.0 6.2": ["outsiders"], "-3.1 -1.9 0.9": ["cardiac"], "10.3 -3.6 -4.6": ["inaugurated"], "-4.2 9.9 8.4": ["override"], "9.8 8.1 4.0": ["dispose"], "16.2 1.5 9.3": ["spawned"], "-1.2 16.3 3.0": ["vulnerabilities"], "5.7 6.1 1.4": ["quitting"], "12.0 6.7 15.9": ["refrigerator"], "12.9 7.2 2.9": ["storing"], "-3.4 11.9 1.2": ["withholding"], "2.9 1.1 3.3": ["empowerment"], "5.5 14.2 2.4": ["activate"], "9.7 2.0 2.6": ["glamorous"], "6.3 27.5 0.3": ["heroic"], "4.8 4.6 2.4": ["fulfillment"], "-6.8 17.1 1.3": ["interpreter"], "4.5 -2.8 7.5": ["coffers"], "-4.5 19.9 5.2": ["homosexual"], "5.3 2.0 5.9": ["tailor"], "2.2 4.6 3.8": ["reps"], "7.1 0.4 6.9": ["spelled"], "8.2 0.0 2.5": ["glamor"], "3.1 15.4 12.3": ["slave"], "-7.0 10.3 7.1": ["attribute"], "4.4 2.5 -0.1": ["infusion"], "8.7 10.4 6.2": ["supreme"], "2.7 5.6 4.1": ["modification"], "6.2 -6.1 8.6": ["pageant"], "2.0 3.4 10.8": ["watershed"], "2.8 7.0 -6.3": ["collaborating"], "15.1 9.6 50.1": ["whale"], "0.3 9.2 7.3": ["emission"], "9.3 2.9 0.1": ["compulsory"], "1.3 2.3 0.3": ["solicit"], "9.1 17.9 13.5": ["kidding"], "7.5 6.7 3.2": ["simultaneous"], "19.6 10.3 22.1": ["belly"], "8.9 -2.0 7.2": ["dent"], "-0.8 -0.3 1.0": ["clocked"], "2.6 18.6 3.7": ["vicinity"], "0.6 18.4 6.7": ["desires"], "13.9 5.0 12.5": ["slam"], "5.1 6.6 5.4": ["aesthetic"], "0.0 10.2 -1.1": ["holed"], "1.2 3.8 6.7": ["stabilization"], "8.4 0.0 11.0": ["busted"], "14.3 4.0 8.5": ["strapped"], "6.4 -5.3 0.4": ["lent"], "9.6 10.0 9.3": ["robbing"], "16.6 -2.4 9.5": ["lavish"], "7.1 4.8 1.1": ["toilets"], "1.9 4.6 11.5": ["veterinarian"], "29.9 1.1 10.6": ["tumbling"], "9.2 9.6 12.1": ["tractor"], "9.3 -3.5 0.4": ["spearheaded"], "8.1 2.5 7.9": ["stocked"], "9.1 7.0 4.2": ["champs"], "-1.1 5.4 12.8": ["umpires"], "-1.1 5.5 9.8": ["backstage"], "-2.2 1.3 3.9": ["drank"], "1.8 2.7 4.0": ["prevalence"], "0.7 13.5 4.0": ["compliment"], "-8.5 15.9 7.3": ["handicap"], "-2.9 3.7 0.0": ["hygiene"], "9.4 0.7 12.3": ["w"], "7.2 13.3 7.9": ["vain"], "9.7 -1.4 16.7": ["bowls"], "8.4 11.2 7.9": ["astronaut"], "-1.9 20.9 8.1": ["selfish"], "9.3 10.7 -0.8": ["slogans"], "-3.2 13.7 -1.6": ["forgiveness"], "7.4 6.9 8.7": ["begging"], "-5.1 4.7 1.6": ["burglaries"], "2.4 9.3 0.8": ["taxing"], "6.7 12.3 2.0": ["chanted"], "3.6 9.9 5.7": ["fewest"], "-5.4 18.3 6.3": ["wisely"], "-3.3 5.6 6.4": ["appraisal"], "12.3 5.5 12.7": ["straw"], "20.3 9.3 16.9": ["tossing"], "3.6 6.2 9.8": ["galleries"], "4.2 -4.8 8.4": ["canceling"], "13.0 9.0 3.6": ["subpoena"], "9.0 2.0 9.8": ["entrants"], "17.9 1.2 24.8": ["crane"], "7.2 25.1 27.1": ["hunter"], "11.7 -6.9 16.5": ["capping"], "18.5 -6.2 -4.7": ["defunct"], "-3.2 11.0 0.5": ["historians"], "-3.4 13.6 1.1": ["ambulances"], "3.7 4.3 14.5": ["tattoo"], "9.1 17.8 10.0": ["scream"], "0.5 8.3 -3.2": ["assert"], "-2.7 9.0 3.0": ["firsthand"], "0.0 9.5 23.1": ["divers"], "-0.5 4.8 11.4": ["scenic"], "-4.8 8.0 1.8": ["inputs"], "21.6 1.0 14.5": ["raft"], "18.5 2.8 -3.9": ["billboards"], "11.1 23.3 33.9": ["shells"], "-1.3 6.4 0.5": ["outburst"], "-1.4 15.9 3.2": ["sacrificed"], "-2.2 13.4 3.9": ["reconcile"], "4.2 16.9 5.4": ["unlucky"], "2.5 8.6 6.8": ["unrealistic"], "2.9 13.6 7.0": ["extortion"], "-2.4 -4.4 9.0": ["biodiesel"], "5.6 16.5 4.9": ["unfavorable"], "9.0 10.5 8.2": ["wildly"], "15.6 11.9 3.7": ["raging"], "0.1 6.5 0.4": ["positives"], "-4.1 19.1 1.9": ["responders"], "8.1 13.4 4.9": ["intensify"], "3.6 -2.5 14.1": ["lbs"], "-4.7 7.5 4.4": ["profanity"], "3.5 -0.0 7.7": ["longevity"], "-0.2 -2.4 8.5": ["citations"], "5.6 4.7 19.9": ["forestry"], "15.7 9.8 10.2": ["downward"], "4.5 3.7 2.0": ["upload"], "5.2 21.5 7.6": ["noble"], "4.8 4.4 -4.8": ["seamlessly"], "0.5 7.5 3.3": ["endeavors"], "3.0 13.9 12.5": ["malware"], "9.7 17.6 6.2": ["bush"], "1.2 3.6 8.1": ["reflective"], "32.2 9.2 6.5": ["ubiquitous"], "5.4 7.9 -4.0": ["defects"], "7.9 -3.1 16.8": ["specials"], "7.9 7.5 16.7": ["ecological"], "5.7 22.5 0.6": ["kidnappers"], "-2.7 -1.1 -2.8": ["accolades"], "-2.2 18.9 7.7": ["intentional"], "1.8 5.8 3.9": ["portraits"], "4.8 10.4 5.4": ["lopsided"], "13.1 10.0 12.1": ["bulls"], "6.9 19.9 7.7": ["angles"], "2.0 23.7 -7.1": ["atrocities"], "2.3 8.4 5.5": ["crossbar"], "3.4 10.5 5.5": ["gossip"], "-1.4 2.2 9.9": ["telecast"], "12.0 11.0 15.1": ["outer"], "9.0 -1.2 2.8": ["invests"], "8.5 -3.8 10.3": ["bagged"], "5.6 4.9 6.9": ["curator"], "7.8 -6.0 1.5": ["showcases"], "-0.6 12.4 6.7": ["enjoyment"], "-1.5 3.6 3.1": ["avail"], "8.4 2.8 5.9": ["contemplating"], "8.2 12.0 0.6": ["flaw"], "16.3 21.3 5.6": ["shadows"], "-6.1 7.1 11.8": ["vaccination"], "9.4 3.8 -2.6": ["exits"], "9.2 12.0 3.8": ["exaggerated"], "-2.9 7.5 4.5": ["swearing"], "7.1 17.3 4.0": ["tunnels"], "7.4 5.1 10.7": ["trucking"], "5.5 11.4 25.8": ["weed"], "1.8 -5.3 24.4": ["dinners"], "19.3 5.9 17.1": ["prized"], "6.4 1.4 9.6": ["massage"], "-0.4 1.0 7.5": ["mayoral"], "5.3 11.0 12.7": ["slope"], "-2.9 8.2 -2.7": ["standby"], "0.1 5.3 4.3": ["tailback"], "9.2 7.7 2.0": ["surround"], "10.1 23.0 -0.9": ["strategically"], "9.0 6.1 2.6": ["surpassing"], "1.9 9.9 1.4": ["disturbance"], "5.2 11.1 11.6": ["nails"], "20.1 5.6 11.0": ["diameter"], "7.4 5.9 9.2": ["choked"], "-0.5 9.5 -4.2": ["differentiate"], "-1.7 3.2 2.3": ["forfeit"], "7.3 21.0 25.5": ["wolves"], "5.6 6.0 4.3": ["forty"], "2.0 8.0 2.8": ["pardon"], "5.6 13.6 8.8": ["defiance"], "2.8 5.7 -4.0": ["strengthens"], "1.6 -1.0 14.2": ["packet"], "14.8 -2.0 4.5": ["botched"], "5.1 -4.4 1.7": ["phased"], "11.9 8.6 18.0": ["melt"], "10.6 7.5 -0.8": ["haven"], "-0.5 7.6 27.0": ["ribs"], "6.3 -6.0 4.8": ["vans"], "13.1 6.3 7.0": ["turbines"], "1.0 7.8 7.8": ["sanction"], "1.2 -1.4 10.4": ["mornings"], "6.4 8.8 -10.4": ["praising"], "18.9 -0.4 0.4": ["folded"], "1.3 4.6 -1.9": ["conductor"], "17.3 14.1 15.5": ["colony"], "11.1 14.0 13.0": ["chill"], "16.2 -1.4 9.4": ["quirky"], "-2.4 0.9 9.8": ["allotted"], "7.3 13.8 11.7": ["contestant"], "9.6 14.9 4.7": ["deepest"], "7.5 8.5 6.1": ["curiosity"], "9.1 11.5 8.7": ["assortment"], "-3.7 3.2 10.3": ["southbound"], "-9.4 -0.4 -3.3": ["evaluations"], "1.1 6.7 2.2": ["divert"], "11.8 4.4 7.2": ["dime"], "-5.5 -1.2 -3.7": ["penned"], "4.0 -2.6 -3.5": ["brokered"], "1.7 4.4 8.0": ["blogging"], "3.2 -0.9 5.5": ["urine"], "4.1 13.1 3.7": ["badge"], "-6.1 0.6 1.4": ["ineligible"], "-0.2 18.1 10.9": ["husbands"], "19.2 5.2 1.7": ["cozy"], "-0.6 6.0 3.0": ["diversion"], "-0.1 3.9 8.3": ["layoff"], "7.6 5.6 5.9": ["snapshot"], "0.8 11.9 2.4": ["negotiator"], "-1.0 3.7 0.6": ["socially"], "18.8 7.4 12.8": ["dense"], "0.4 3.3 1.5": ["concentrations"], "-0.7 8.8 14.9": ["skiers"], "0.7 5.4 15.5": ["paycheck"], "9.0 43.8 6.1": ["guerrillas"], "12.7 0.6 8.4": ["nude"], "7.1 17.4 0.4": ["mechanic"], "18.8 19.6 17.3": ["prince"], "-4.1 2.6 4.5": ["pediatric"], "-2.6 7.6 28.6": ["harvested"], "10.2 8.1 17.1": ["soda"], "1.4 -7.2 -2.2": ["tabled"], "14.1 6.7 2.6": ["engulfed"], "6.2 -2.5 3.9": ["rentals"], "7.5 5.0 4.6": ["malls"], "-2.1 1.6 11.7": ["discretionary"], "13.0 17.9 6.2": ["manipulate"], "5.5 17.1 3.7": ["cockpit"], "4.0 14.1 0.6": ["cleric"], "-0.6 0.0 4.3": ["l"], "10.7 6.8 0.4": ["orchestrated"], "13.6 -0.4 10.9": ["strips"], "-5.9 28.4 4.4": ["wartime"], "9.2 3.9 9.5": ["refreshments"], "-1.4 19.3 8.4": ["separatist"], "7.6 5.9 25.3": ["sandwiches"], "16.9 13.4 4.5": ["fend"], "0.7 11.3 3.4": ["booed"], "8.4 4.6 16.6": ["bakery", "talento"], "-2.8 1.0 -0.8": ["doubted"], "-3.4 5.4 -5.1": ["facilitating"], "-0.2 21.4 10.1": ["dividing"], "0.2 12.3 0.7": ["striving"], "-0.5 3.6 13.1": ["slack"], "11.7 0.4 6.6": ["edging", "comapred"], "3.8 4.8 11.9": ["acoustic"], "5.1 7.9 6.2": ["pullback"], "15.6 5.5 -5.6": ["marketer"], "17.8 2.2 9.9": ["watchers"], "-1.6 6.9 16.1": ["racers"], "3.7 5.5 9.1": ["rounder"], "9.9 33.3 18.5": ["sword"], "7.6 3.3 -2.0": ["browsing"], "-0.8 4.2 4.5": ["economical"], "13.9 7.2 13.9": ["slugger"], "2.6 2.4 6.8": ["extras"], "-2.6 -4.9 6.1": ["reopening"], "6.2 7.5 7.4": ["lessen"], "3.2 -4.2 1.9": ["converged"], "3.2 7.5 13.5": ["groove"], "5.6 2.7 3.4": ["redundant"], "14.0 12.3 24.4": ["elephants"], "4.4 6.8 13.9": ["weights"], "-1.8 -2.4 2.0": ["rescheduled"], "7.9 8.6 10.0": ["devised"], "-4.6 -3.3 -2.1": ["confidentiality"], "12.5 6.8 8.9": ["importing"], "7.9 9.5 5.9": ["abstract"], "1.6 4.5 12.5": ["colt"], "10.1 2.8 2.6": ["eco"], "6.7 27.8 -1.5": ["liberation"], "17.2 11.3 4.0": ["vigorously"], "14.3 2.4 9.3": ["discarded"], "-0.4 25.9 5.5": ["inflicted"], "1.1 11.3 5.0": ["odor"], "-4.3 6.4 7.4": ["impacting"], "-3.3 3.2 10.2": ["allocate"], "5.0 -0.2 0.8": ["interchange"], "2.0 13.3 -2.3": ["awake"], "-1.4 5.7 -0.2": ["resides"], "3.7 5.9 4.3": ["seizures"], "7.3 4.6 0.2": ["locking"], "5.9 5.3 2.9": ["perks"], "6.1 8.9 -1.0": ["chatting"], "2.3 9.9 -4.0": ["pains"], "17.4 27.9 21.8": ["predators"], "1.4 15.6 7.8": ["cynical"], "24.5 7.3 6.2": ["depicting"], "13.9 8.3 9.7": ["messy"], "2.8 0.9 2.1": ["tuned"], "-8.3 6.9 6.8": ["mitigation"], "4.3 18.4 10.0": ["learns"], "-4.6 9.6 10.1": ["wit"], "6.4 12.3 16.1": ["expedition"], "4.3 0.1 12.1": ["entitlement"], "9.6 15.4 12.7": ["ancestors"], "-2.0 12.7 0.6": ["intersections"], "2.0 10.8 11.2": ["backhand"], "15.5 -1.8 5.4": ["rollout"], "-1.0 4.6 0.4": ["psychiatrist"], "0.4 15.5 8.6": ["traits"], "5.3 11.2 11.2": ["groom"], "7.0 6.3 11.1": ["lays"], "-4.5 7.8 5.1": ["inactive"], "9.4 8.0 4.1": ["brunt"], "11.6 6.9 5.4": ["molecular"], "18.6 16.4 8.4": ["remnants"], "-0.8 20.0 -4.5": ["victorious"], "25.7 2.4 4.8": ["marquee"], "-6.5 0.1 14.4": ["condominium"], "-3.3 2.2 4.9": ["accommodations"], "0.5 10.2 20.4": ["livelihood"], "6.5 41.4 10.1": ["warfare"], "5.4 -2.9 -1.5": ["encompasses"], "1.0 -0.7 -2.7": ["reins"], "5.0 0.6 6.0": ["complied"], "8.2 11.7 0.0": ["vastly"], "15.1 5.1 17.1": ["eyed"], "1.7 4.2 5.1": ["restrictive"], "7.7 18.1 8.3": ["cries"], "17.0 3.9 1.7": ["plasma"], "4.8 16.2 2.2": ["communal"], "25.6 4.9 6.2": ["resemble"], "-3.8 0.7 9.7": ["northbound"], "2.9 5.3 -0.1": ["birdied"], "-9.6 1.7 8.1": ["officiating"], "1.8 6.4 5.8": ["selectors"], "10.1 14.0 -0.8": ["embassies"], "2.4 -2.0 3.7": ["parcels"], "10.5 7.6 9.7": ["horn"], "25.1 30.0 36.2": ["creature"], "10.0 12.8 12.0": ["cliff"], "4.0 27.4 -3.7": ["paramilitary"], "10.4 11.5 23.2": ["biting"], "2.3 11.6 5.8": ["query"], "6.5 6.3 9.2": ["gutted", "guilelessly"], "7.0 9.4 10.0": ["evacuees"], "6.1 10.1 18.4": ["leaf"], "5.2 14.4 4.5": ["looting"], "9.2 9.0 5.3": ["coffin"], "16.1 7.3 2.7": ["noisy"], "10.2 6.2 9.3": ["unfold"], "0.0 6.1 10.7": ["prostitutes"], "9.3 7.5 -1.7": ["fray"], "1.3 14.4 7.7": ["shades"], "5.1 11.9 4.0": ["thwarted"], "-7.9 6.4 2.0": ["sung"], "0.3 28.1 4.1": ["extremism"], "1.4 16.7 2.4": ["admiration"], "7.5 4.8 10.5": ["needle"], "4.9 27.0 9.5": ["senses"], "3.3 22.1 6.6": ["arrogant"], "3.2 3.6 9.8": ["skated"], "13.0 8.4 2.3": ["boasted"], "8.2 -0.2 -3.2": ["probing"], "10.0 6.5 -4.1": ["purported"], "-3.8 16.2 -6.1": ["radios"], "5.6 13.2 10.8": ["motorist"], "3.9 11.2 5.6": ["airwaves"], "13.9 1.2 16.9": ["upstream"], "6.6 5.6 -1.5": ["integral"], "10.8 5.3 1.7": ["removes"], "2.7 2.0 2.3": ["managerial"], "11.6 3.6 8.2": ["insert"], "2.5 26.1 3.6": ["operatives"], "21.5 11.6 11.2": ["smashing"], "-0.5 7.2 28.2": ["flour"], "0.2 13.3 14.9": ["pesticides"], "4.2 0.5 3.9": ["dissolved"], "33.4 5.9 7.4": ["towering"], "-2.4 5.0 2.7": ["encryption"], "7.0 -1.0 6.2": ["streamlined"], "15.7 16.4 7.2": ["thwart"], "10.4 9.9 13.2": ["slows"], "8.8 5.6 -0.6": ["principally"], "-1.9 -2.2 1.6": ["endorsements"], "-0.6 16.5 -1.4": ["insulting"], "13.3 11.7 6.3": ["stark"], "11.8 3.8 8.2": ["drifted"], "-4.1 28.2 6.1": ["lieutenant"], "-0.4 2.7 2.7": ["heed"], "13.9 3.6 21.8": ["sliced"], "5.0 2.2 0.3": ["utilizes"], "5.8 17.5 5.8": ["alley"], "6.7 1.5 0.7": ["recycle"], "1.0 6.1 6.0": ["fingerprints"], "1.2 17.6 0.0": ["mobilize"], "-7.5 9.3 2.6": ["disagreements"], "-1.5 11.5 16.8": ["caucuses"], "13.6 9.5 9.9": ["harmless"], "9.5 -1.6 2.8": ["amounting"], "-3.7 -1.3 -6.9": ["examinations"], "-3.2 -1.1 15.6": ["hospice"], "2.4 18.8 11.8": ["clan"], "3.0 22.9 5.7": ["deterrent"], "-0.6 0.1 10.5": ["condoms"], "30.8 5.6 -0.4": ["salesman"], "1.1 13.1 4.5": ["dispatcher"], "-4.8 -4.1 -1.4": ["informative"], "12.9 -1.4 15.6": ["raffle"], "5.0 5.1 7.0": ["defied"], "0.8 8.3 6.6": ["borrowings"], "-3.1 -3.4 -3.4": ["chairperson"], "10.6 1.8 2.7": ["dogged"], "6.8 5.0 -0.9": ["urgently"], "6.8 7.2 13.9": ["knot"], "5.8 5.5 4.6": ["alarmed"], "10.8 8.4 7.2": ["pornography"], "15.0 17.9 8.1": ["guts"], "9.6 6.2 8.3": ["ceremonial"], "-1.7 2.7 3.1": ["restrained"], "-0.0 1.0 6.3": ["disadvantaged"], "3.9 12.4 -2.5": ["safest"], "-8.0 3.4 -3.7": ["conveyed"], "16.1 8.6 9.3": ["hovering"], "13.1 -3.5 8.8": ["stirred"], "0.8 25.7 8.0": ["detainee"], "-3.2 7.2 23.3": ["soybeans"], "-7.2 5.1 5.4": ["dues"], "10.5 8.9 10.5": ["bargains"], "3.0 1.8 10.5": ["fundraisers"], "8.2 21.5 11.8": ["culprit"], "-2.9 6.2 8.8": ["bouts"], "0.7 19.9 13.0": ["daylight"], "7.1 8.3 6.0": ["telephony"], "8.4 6.1 -4.9": ["derivative"], "8.2 3.1 12.6": ["fencing"], "8.8 4.9 16.8": ["tow"], "16.9 8.4 6.0": ["epicenter"], "9.7 23.0 12.7": ["souls"], "9.3 11.6 15.5": ["bureaucrats"], "-4.4 -2.6 12.8": ["births"], "-1.6 5.5 5.4": ["demographics"], "12.3 20.4 6.4": ["awe"], "-3.9 -1.0 4.9": ["revisit"], "13.9 3.6 4.6": ["soaked"], "2.8 1.7 -0.1": ["min"], "7.4 11.3 12.8": ["mat"], "2.1 6.4 5.7": ["diversification"], "3.2 1.8 -7.3": ["compatibility"], "16.8 7.7 20.5": ["chunks"], "5.2 11.8 8.4": ["interfering"], "14.7 2.6 -0.3": ["pledging"], "5.0 10.7 2.0": ["erratic"], "7.4 7.9 16.4": ["rink"], "-4.1 -2.6 4.0": ["throughput"], "-4.2 -1.6 2.2": ["cautions"], "4.6 -6.7 10.0": ["limbo"], "-6.1 4.2 -0.6": ["afforded"], "-4.8 2.4 2.1": ["sober"], "3.5 9.3 1.7": ["charismatic"], "2.1 4.4 9.3": ["indie"], "-2.7 21.0 0.9": ["remembering"], "8.2 7.0 3.6": ["pleasing"], "-7.3 -3.3 -4.9": ["authored"], "2.9 6.9 5.1": ["ii", "bested"], "-4.0 11.2 2.2": ["portrayal"], "7.3 13.9 3.9": ["appalling"], "15.1 4.6 1.8": ["startling"], "5.8 17.4 6.9": ["misguided"], "16.5 8.0 5.2": ["looms"], "7.9 5.2 6.7": ["prohibition"], "-2.7 -5.2 3.4": ["remanded"], "3.3 -0.7 3.9": ["gymnastics"], "14.6 3.1 6.8": ["scaling"], "10.7 14.8 22.7": ["drift"], "-3.1 4.5 3.2": ["procedural"], "7.5 5.8 6.9": ["pleading"], "12.7 5.1 8.1": ["heats"], "2.7 9.7 2.3": ["administrations"], "23.5 6.0 8.7": ["replica"], "4.7 2.1 1.2": ["deaf"], "11.4 26.4 11.5": ["curse"], "10.2 3.5 5.0": ["cooled"], "13.8 16.9 4.3": ["inadvertently"], "5.5 -2.8 2.0": ["steered"], "9.4 7.9 20.6": ["texture"], "13.7 -0.8 9.3": ["magnet"], "7.2 5.9 4.5": ["gritty"], "-0.5 4.9 -2.8": ["mentioning"], "5.3 6.4 1.8": ["u"], "0.9 1.0 -0.3": ["luxurious"], "6.0 11.8 11.9": ["chilly"], "4.0 -2.4 0.8": ["publicized"], "2.6 12.1 -6.0": ["transmit"], "0.8 14.0 1.6": ["naive"], "9.3 8.3 2.6": ["roadmap"], "6.4 8.7 8.6": ["bruising"], "2.0 14.1 3.2": ["handcuffed"], "1.8 7.3 0.2": ["vigil"], "-5.0 -0.5 10.7": ["minivan"], "4.2 17.5 4.5": ["dangerously"], "4.9 6.9 10.3": ["tempered"], "-6.3 9.5 16.0": ["precipitation"], "13.1 7.3 6.6": ["spelling"], "16.1 4.8 13.6": ["gloom"], "9.1 23.3 4.1": ["sabotage"], "5.9 12.8 -2.2": ["distractions"], "0.7 5.1 17.4": ["gubernatorial"], "2.8 10.7 1.5": ["possesses"], "0.3 0.5 1.7": ["parity"], "-0.1 6.8 3.8": ["exhaust"], "13.2 -1.4 5.0": ["brisk"], "3.6 28.3 0.7": ["believers"], "4.1 5.4 4.3": ["dignitaries"], "-1.1 4.2 -0.1": ["testifying"], "3.4 6.3 6.9": ["defaults"], "6.1 5.8 6.1": ["bribe"], "5.4 -0.2 -0.1": ["dismissing"], "8.5 -1.0 6.7": ["arranging"], "11.7 20.5 8.7": ["pal"], "11.4 8.4 6.7": ["surreal"], "-3.6 3.0 -1.9": ["playback"], "-2.3 10.6 3.3": ["rendition"], "1.5 14.4 2.5": ["succeeding"], "8.5 17.7 -1.6": ["salute"], "0.3 4.3 5.5": ["explanations"], "6.1 12.8 8.3": ["likewise"], "7.8 5.5 4.8": ["leaderboard"], "18.8 2.8 5.7": ["plaza"], "-0.5 10.0 0.1": ["rift"], "9.5 6.1 17.8": ["liner"], "3.1 -2.3 7.1": ["circuits"], "-7.6 5.8 10.0": ["closings"], "13.2 8.2 9.5": ["protracted"], "-8.2 7.4 2.2": ["poems"], "33.9 2.7 6.9": ["miniature"], "5.2 26.7 5.1": ["grenades"], "12.8 8.0 5.2": ["whipped"], "9.3 2.6 8.8": ["sealing"], "2.5 7.3 0.2": ["construed"], "4.0 -1.6 -1.5": ["hotline"], "15.4 24.0 4.1": ["terrifying"], "-5.8 2.3 5.3": ["pianist"], "1.0 -4.3 3.0": ["grad"], "-0.8 22.4 11.4": ["airspace"], "13.8 8.0 -0.2": ["flashed"], "2.5 14.5 8.0": ["insecurity"], "4.0 9.0 31.2": ["harvesting"], "8.4 8.7 14.9": ["jackpot"], "6.5 -4.1 12.9": ["weeklong"], "10.1 4.9 4.8": ["replicate"], "-7.4 -0.6 12.1": ["bonding"], "2.0 10.2 11.1": ["payrolls"], "7.6 18.7 3.9": ["deserted"], "6.9 10.1 5.5": ["semis"], "0.0 12.2 6.3": ["mindful"], "9.3 15.7 12.3": ["throne"], "2.5 -0.2 26.2": ["quotas"], "2.1 17.1 2.6": ["rooting"], "9.0 7.4 8.5": ["periodic"], "-1.5 21.6 4.9": ["morality"], "16.0 29.5 25.8": ["pirate"], "2.2 17.2 12.5": ["ego"], "8.2 12.4 6.9": ["embargo"], "14.0 4.3 0.6": ["depot"], "3.3 1.7 -7.5": ["accessibility"], "3.9 -2.2 1.9": ["culmination"], "2.4 15.2 2.3": ["possessed"], "6.1 9.7 6.3": ["insure", "steepness"], "-2.1 7.7 3.2": ["recounted"], "4.5 18.9 4.6": ["mantra"], "-3.7 9.5 2.1": ["attain"], "22.4 11.4 3.4": ["shining"], "4.5 15.3 11.2": ["arbitrary"], "4.6 6.6 6.1": ["imply"], "-1.3 -2.3 7.3": ["veterinary"], "21.4 8.1 7.4": ["guru"], "-0.4 12.5 5.8": ["traveler"], "6.5 8.6 2.6": ["hugged"], "10.6 12.1 3.3": ["exploits"], "6.5 9.9 9.6": ["ashes"], "6.2 6.8 3.6": ["staffer"], "3.8 1.0 8.7": ["hoops"], "6.9 5.4 14.2": ["painter"], "8.8 0.3 2.0": ["chartered"], "14.0 -4.2 5.4": ["upped"], "10.4 18.1 6.8": ["greatness"], "0.8 5.7 0.1": ["saddened"], "-5.8 2.5 -2.2": ["appointing"], "6.2 -0.2 8.1": ["spurt"], "-3.2 3.5 2.6": ["summed"], "5.5 15.2 15.2": ["chin"], "9.2 6.8 12.2": ["gem"], "4.3 13.9 -3.1": ["acknowledgment"], "16.4 9.5 11.9": ["freak"], "2.8 21.8 5.7": ["forbidden"], "14.3 14.1 -0.3": ["loudly", "localises"], "-2.9 3.2 -1.2": ["renovate"], "12.6 3.9 1.4": ["longstanding"], "7.5 17.1 -1.1": ["unconventional"], "8.8 -7.0 0.9": ["derailed"], "8.4 10.6 12.1": ["toast"], "1.1 5.5 1.4": ["hassle"], "9.6 -6.2 7.0": ["coincided"], "-4.5 -0.6 -3.1": ["clarification"], "3.2 2.7 -4.1": ["browse"], "9.0 7.2 9.4": ["mired"], "12.7 11.4 12.5": ["volcano"], "-6.0 9.6 -6.3": ["communicated"], "4.8 -0.1 9.1": ["favoring"], "8.6 4.2 1.4": ["prohibiting"], "10.5 8.5 12.9": ["extinction"], "3.3 11.1 5.5": ["lookout"], "6.5 2.7 19.0": ["arthritis"], "15.0 6.9 29.3": ["tasty"], "6.3 21.0 3.2": ["resisting"], "6.4 1.0 4.8": ["discs"], "3.9 0.4 6.9": ["endowment"], "0.7 4.0 5.1": ["biopharmaceutical"], "-3.4 -1.2 0.3": ["garner"], "4.2 5.4 19.8": ["roses"], "7.8 7.4 5.1": ["customize"], "1.1 -2.6 -2.8": ["specification"], "-5.4 11.6 -1.4": ["grievances"], "13.0 10.5 1.2": ["recognizable"], "9.7 10.5 10.5": ["seismic"], "3.7 -4.0 16.5": ["baht"], "18.8 0.9 2.5": ["bowed"], "20.9 5.9 0.1": ["foray"], "-3.2 9.5 1.5": ["meteorologist"], "-0.7 10.6 4.1": ["composure"], "2.0 11.3 1.3": ["sync"], "11.7 -0.1 6.8": ["dashed"], "-1.3 6.0 7.8": ["resellers"], "3.5 14.9 4.6": ["geographical"], "-2.6 -3.2 5.7": ["convene"], "0.7 7.7 4.2": ["excel"], "-4.1 4.6 2.2": ["correlation"], "6.0 -4.5 3.0": ["overseen"], "-6.9 13.3 1.9": ["apprehended"], "11.7 11.7 34.9": ["ducks"], "-0.1 15.1 0.2": ["unlocked"], "6.5 5.1 4.9": ["unfinished"], "8.4 2.5 10.7": ["et"], "8.7 13.3 0.1": ["logistical"], "-0.1 4.0 12.9": ["textbook"], "2.3 5.0 1.0": ["contending"], "10.3 -1.7 6.3": ["storey"], "6.7 14.2 1.1": ["detonated"], "2.9 6.2 1.2": ["footballer"], "2.4 13.7 9.3": ["beforehand"], "-5.3 7.5 8.0": ["compassionate"], "8.2 42.3 2.2": ["guerrilla"], "-7.4 14.1 5.8": ["preventive"], "8.3 11.0 17.2": ["puppy"], "9.7 4.2 4.5": ["warmed"], "-1.4 13.6 49.2": ["trout"], "1.7 5.4 10.2": ["duplicate"], "2.4 15.6 23.9": ["vegetation"], "8.1 4.3 7.5": ["backpack"], "8.9 4.5 0.2": ["gymnasium"], "5.1 11.9 3.0": ["adjoining"], "13.2 4.9 9.3": ["bracing"], "11.1 2.4 9.1": ["newborn"], "16.7 16.1 5.5": ["dismantle"], "7.0 7.8 7.6": ["locker"], "15.3 9.4 1.7": ["expansive"], "5.8 5.6 12.7": ["punk"], "6.3 5.2 3.3": ["outage"], "8.0 6.7 4.7": ["tampering"], "-1.8 16.5 6.6": ["backfield"], "0.3 8.2 8.2": ["hers"], "12.8 10.8 15.3": ["hop"], "13.1 10.9 19.6": ["eats"], "20.5 1.3 16.2": ["sculptures"], "18.2 13.5 12.5": ["crippling"], "7.2 12.6 -4.5": ["infringement"], "18.9 7.2 9.2": ["bailouts"], "8.0 9.7 11.1": ["swollen"], "16.5 6.5 0.0": ["probes"], "31.2 26.8 23.3": ["beast"], "8.8 7.6 3.6": ["newsroom"], "3.9 18.5 0.9": ["kindness"], "-2.7 8.6 -1.9": ["empowered"], "-0.6 5.7 19.2": ["juveniles"], "11.3 8.7 1.8": ["seizing"], "13.2 2.5 3.5": ["sparks"], "3.4 8.6 -1.5": ["junction"], "11.6 13.4 7.0": ["pathetic"], "11.8 2.8 3.6": ["quell"], "4.7 21.6 8.8": ["temptation"], "-0.6 11.7 0.6": ["harassed"], "9.9 5.5 2.8": ["rampage"], "11.5 4.0 8.5": ["antics"], "7.5 1.7 22.0": ["basin"], "6.4 19.9 5.6": ["characteristic"], "13.9 16.8 14.9": ["angel"], "17.0 12.7 9.9": ["masked"], "-1.0 4.0 7.9": ["upstate"], "4.4 10.2 7.4": ["precinct"], "10.0 3.6 2.0": ["capsule"], "6.6 12.6 10.4": ["timer"], "12.0 2.2 6.6": ["amidst"], "-0.8 20.8 -0.8": ["patriotism"], "-0.3 9.3 3.6": ["mattered", "developemnt"], "-0.2 4.9 4.4": ["establishes"], "7.0 5.6 11.5": ["buckets"], "5.1 14.1 15.1": ["jaw"], "-6.5 -2.8 3.3": ["notebooks"], "1.8 10.7 4.2": ["repercussions"], "8.3 18.1 12.5": ["limbs"], "7.7 12.3 3.7": ["revered"], "-2.4 5.6 1.6": ["ratification"], "-0.6 4.3 15.3": ["swam"], "5.9 13.4 3.2": ["rude"], "6.4 3.1 1.0": ["cheated"], "18.5 0.9 9.3": ["tubes"], "11.7 7.1 4.4": ["scams"], "-3.5 3.2 -4.1": ["appreciates"], "6.8 6.8 6.6": ["abnormal"], "3.1 3.2 5.4": ["impetus"], "-2.3 5.3 -4.0": ["resigning"], "1.2 19.7 3.6": ["suppress"], "-1.8 6.0 0.1": ["moderators"], "11.0 4.1 4.4": ["flawless"], "17.9 20.2 2.0": ["topple"], "-0.0 14.6 2.5": ["extraordinarily"], "13.6 37.3 10.8": ["villain"], "15.9 2.4 10.7": ["halting"], "1.2 25.2 6.6": ["hostility"], "7.1 14.4 3.0": ["announcer"], "-1.2 10.4 0.8": ["elevation"], "-7.0 13.9 4.7": ["grieving"], "9.3 13.4 1.1": ["corridors"], "7.5 -1.3 5.3": ["trendy"], "6.2 12.0 -0.2": ["avenue"], "2.2 6.1 8.2": ["outages"], "2.6 4.3 7.6": ["manageable"], "9.3 6.5 6.9": ["disappoint"], "5.5 24.8 1.3": ["waged"], "4.7 6.7 3.6": ["bumps"], "-0.6 12.4 1.6": ["friction"], "21.8 8.0 5.7": ["shedding"], "2.6 15.4 9.1": ["heel"], "-1.3 12.2 0.0": ["perjury"], "3.5 6.4 12.1": ["wrestle"], "3.7 7.8 -7.2": ["misled"], "10.8 12.4 -0.2": ["exploiting"], "5.7 7.7 27.7": ["lumber"], "3.2 6.9 -0.9": ["bathrooms"], "8.1 13.6 20.5": ["blade"], "7.3 5.2 -3.5": ["scans"], "5.5 12.8 5.0": ["brilliantly"], "5.4 14.7 -1.0": ["reacts"], "13.6 10.9 3.1": ["nicknamed"], "7.9 2.7 2.1": ["modular"], "2.0 9.6 9.8": ["storytelling"], "15.5 15.2 13.2": ["crawl"], "-5.8 10.7 4.7": ["rehearsal"], "6.6 11.4 -0.9": ["quickest"], "3.3 3.6 0.2": ["hails"], "-3.6 -4.6 8.9": ["cancellations"], "8.4 7.9 15.4": ["creations"], "-3.1 7.4 17.4": ["snowfall"], "-1.8 10.1 4.5": ["hedging"], "5.7 10.9 7.8": ["recruiters"], "6.4 13.2 10.9": ["deepen"], "-3.6 17.9 0.4": ["storyline"], "26.8 16.2 26.0": ["worm"], "-2.8 1.4 4.2": ["partying"], "-4.6 11.8 8.4": ["ethnicity"], "6.5 22.1 23.4": ["weeds"], "11.8 10.2 8.1": ["trajectory"], "2.7 9.9 2.6": ["incur"], "16.4 9.3 12.0": ["disappearing"], "4.5 9.3 9.0": ["levee"], "10.4 -2.5 1.0": ["recoup"], "2.0 11.4 3.1": ["prestige"], "6.9 -3.1 9.5": ["suspending"], "6.2 20.9 7.4": ["isolate"], "-1.8 3.0 2.3": ["slayings"], "6.6 22.8 17.0": ["mosquitoes"], "-5.5 -0.6 1.8": ["scripts"], "4.1 14.5 7.4": ["swear"], "-3.9 -2.4 -4.3": ["researched"], "11.0 16.5 12.0": ["madness"], "9.7 5.5 27.7": ["seals"], "2.2 5.4 0.0": ["designate"], "-1.8 9.0 11.6": ["getaway"], "6.9 -0.0 0.9": ["conform"], "12.1 1.8 0.8": ["outsourced"], "-4.3 0.1 8.4": ["summers"], "-0.4 1.7 10.5": ["nonprofits"], "-0.1 -4.0 16.7": ["prom"], "-5.9 15.3 -3.1": ["deeds"], "23.5 5.8 -1.3": ["billboard"], "0.9 5.5 7.2": ["hybrids"], "5.0 6.2 6.9": ["remedies"], "17.4 16.6 18.2": ["dude"], "22.7 13.4 0.2": ["blasting"], "3.2 18.7 6.6": ["outsider"], "22.7 4.0 10.2": ["dazzling"], "-1.1 5.0 0.7": ["crossover"], "-2.3 -0.3 3.1": ["foregoing"], "8.1 3.2 20.9": ["netting"], "-9.9 10.6 5.0": ["screenplay"], "16.4 -5.2 -3.2": ["pioneered"], "-1.2 0.9 -4.6": ["staffed"], "-0.3 6.5 0.5": ["liquidation"], "22.2 -1.0 11.0": ["pavilion"], "5.7 16.6 2.0": ["passer"], "-2.7 14.6 -2.2": ["translator"], "4.7 5.8 1.7": ["ramifications"], "2.2 16.5 -1.5": ["devotion"], "10.4 8.2 1.5": ["wandering"], "7.3 11.0 5.7": ["nowadays"], "13.6 14.4 28.6": ["oceans"], "23.3 9.6 11.4": ["mascot"], "9.0 4.4 4.5": ["benches"], "-3.5 12.1 4.7": ["genres"], "5.3 2.6 -2.0": ["leveraged"], "10.8 20.5 4.5": ["penetrate"], "8.1 14.8 2.9": ["locating"], "3.3 8.9 0.5": ["honorary"], "12.0 29.8 4.5": ["airborne"], "3.4 7.6 -1.1": ["unmatched"], "9.7 0.1 11.6": ["piling"], "1.2 19.4 1.8": ["humiliation"], "16.6 19.7 5.7": ["suck"], "15.8 -2.9 3.2": ["cosmetics"], "2.1 10.3 9.6": ["escalate"], "5.5 2.7 15.6": ["skirt"], "-1.6 4.2 -7.6": ["copied"], "0.8 7.0 -2.4": ["competence"], "2.5 4.4 5.2": ["valve"], "-0.2 2.0 2.0": ["upsets"], "3.7 14.5 0.3": ["mourners"], "-7.8 9.1 5.1": ["vaccinated"], "2.6 -8.4 4.6": ["symposium"], "10.2 8.9 7.1": ["taller"], "4.8 9.4 3.7": ["sweeps"], "-1.7 17.8 1.8": ["nationalist"], "-5.4 11.5 1.6": ["taxable"], "-2.5 13.5 4.1": ["discourse"], "1.4 18.1 4.5": ["teamwork"], "11.8 12.3 4.6": ["upright"], "15.5 5.6 7.7": ["unfolding"], "10.6 8.6 8.0": ["brightest"], "6.3 9.5 47.7": ["fisherman"], "13.1 6.3 1.2": ["queue"], "-0.3 9.9 -0.5": ["heartbreaking"], "7.2 14.3 1.4": ["manned"], "3.3 7.2 2.3": ["impressions"], "21.5 2.2 -0.7": ["logos"], "1.6 9.5 5.5": ["amusing"], "8.4 14.1 1.4": ["sprayed"], "-1.9 5.5 4.5": ["pessimistic"], "7.4 8.3 12.9": ["rigid"], "14.0 5.0 18.3": ["swell"], "0.0 -0.8 2.4": ["postings"], "-1.2 8.5 9.3": ["acreage"], "1.1 -4.0 -5.7": ["collaborated"], "9.4 13.9 5.3": ["waking"], "24.2 4.6 5.7": ["dominates"], "-2.0 8.3 5.8": ["disregard"], "2.0 4.8 -1.2": ["chapel"], "0.2 11.1 0.3": ["upsetting"], "5.3 11.5 12.2": ["unhealthy"], "1.6 2.6 4.8": ["fellowship"], "10.4 10.4 0.8": ["disgruntled"], "0.3 0.4 23.6": ["hay"], "-6.1 12.3 32.5": ["grapes"], "-2.9 0.3 -1.7": ["wording"], "7.5 12.2 1.6": ["wholly"], "16.6 9.8 -0.2": ["merging"], "3.0 4.6 5.2": ["authentication"], "-1.8 9.1 11.9": ["citation"], "-1.5 8.6 16.8": ["reproductive"], "3.6 -0.0 -0.8": ["lecturer"], "7.3 15.5 4.1": ["apartheid"], "7.8 13.8 8.5": ["calmly"], "5.3 13.7 12.9": ["sequences"], "-2.2 3.7 -0.2": ["shutouts"], "14.9 19.1 25.8": ["bees"], "6.8 9.5 5.5": ["uneasy"], "14.7 6.4 15.7": ["crystal"], "16.6 1.3 13.1": ["hauling"], "15.6 19.2 7.5": ["planets"], "7.2 24.9 8.6": ["helpless"], "5.3 -0.7 -4.2": ["dedicate"], "6.9 -3.0 2.8": ["discontinued"], "-5.9 16.4 -7.6": ["assassinated"], "-5.4 6.0 3.7": ["obligated"], "3.5 6.4 3.2": ["senate"], "-3.6 12.0 1.2": ["arises"], "10.2 2.8 2.0": ["clears"], "-6.1 6.7 4.7": ["mentors"], "17.4 8.1 10.2": ["continental"], "-2.7 7.2 6.1": ["honeymoon"], "1.0 -2.0 17.9": ["fertility"], "-7.9 13.3 0.2": ["teachings"], "16.0 12.3 14.1": ["grinding"], "-1.0 9.3 0.4": ["deficiencies"], "-0.2 4.9 0.8": ["squandered"], "0.8 9.3 -1.7": ["coma"], "-1.9 25.1 -1.1": ["betrayed"], "13.2 12.4 0.9": ["overtake"], "10.5 2.2 -0.8": ["merchandising"], "24.6 6.7 8.7": ["rigged"], "-2.0 18.9 6.7": ["circumstance"], "17.3 23.3 5.6": ["pretending"], "3.7 11.2 14.7": ["temper"], "-0.6 -2.9 2.2": ["waive"], "1.9 4.0 8.6": ["blended"], "6.0 8.9 2.6": ["overlook", "vibrator"], "8.3 8.1 6.1": ["numbered"], "18.8 12.2 8.6": ["flashing"], "4.9 -2.5 12.1": ["rodeo"], "-7.1 9.1 -6.2": ["traumatic"], "7.6 12.0 5.2": ["leukemia"], "-2.2 35.0 1.4": ["airstrikes"], "5.7 14.0 2.7": ["uncover"], "-2.5 25.4 2.3": ["servant"], "4.2 4.8 3.1": ["activism"], "2.7 -4.0 2.5": ["invitations"], "8.0 4.7 6.0": ["fixes"], "0.7 -0.8 25.5": ["smoked"], "12.9 -1.8 9.4": ["fetch"], "6.0 0.2 8.6": ["materialize"], "5.3 15.8 8.4": ["cheat"], "0.7 12.1 3.0": ["ailments"], "-8.2 -4.8 7.5": ["weekdays"], "4.4 9.0 17.0": ["collar"], "5.1 22.2 1.6": ["intercept"], "0.3 0.1 -5.9": ["endorsing"], "21.4 8.6 -1.1": ["ripping"], "-5.6 5.4 8.7": ["finishers"], "1.6 8.1 20.1": ["grains"], "2.4 3.9 13.5": ["beard"], "7.0 -1.0 -0.1": ["sorting"], "5.4 7.4 10.2": ["cylinder"], "9.0 6.2 8.8": ["waning"], "1.2 12.8 -4.3": ["defect"], "-2.8 11.1 5.5": ["convict"], "-4.6 3.2 10.3": ["bpd"], "-7.2 -1.6 13.0": ["weekday"], "3.1 14.2 3.2": ["nominal"], "3.8 6.0 3.9": ["ecstatic"], "5.8 6.5 -5.4": ["shocks"], "13.9 13.8 5.4": ["protestors"], "17.4 12.8 8.1": ["hacking"], "1.0 4.2 8.6": ["reinsurance"], "-4.8 5.6 22.0": ["cooks"], "-3.4 6.6 -5.5": ["exemplary"], "9.9 35.6 17.0": ["armor"], "4.5 12.4 7.6": ["avalanche"], "-1.0 14.5 14.3": ["resentment"], "5.7 3.7 9.0": ["migrate"], "9.4 14.6 0.7": ["concealed"], "10.9 6.0 6.6": ["filtering"], "1.6 10.1 -3.4": ["redeem"], "5.5 20.8 1.3": ["regimes"], "4.3 7.3 3.0": ["stereo"], "1.1 0.6 6.3": ["drying"], "8.3 8.9 7.2": ["depressing"], "6.9 22.0 5.4": ["dissidents"], "1.2 10.1 7.5": ["athleticism"], "2.5 11.5 17.6": ["earmarks"], "10.5 35.9 8.7": ["warrior"], "19.7 13.2 10.8": ["prowess"], "29.4 15.1 27.4": ["monkey"], "-4.6 10.3 4.1": ["pragmatic"], "4.2 5.7 -1.3": ["disposed"], "3.5 19.2 2.2": ["perceive"], "2.7 9.1 5.9": ["hinder"], "8.0 3.7 10.2": ["flair"], "-4.1 5.9 9.9": ["filly"], "4.4 14.1 9.9": ["patron"], "2.5 3.5 6.8": ["ordinances"], "6.5 2.7 6.6": ["mismanagement", "netto"], "3.0 8.7 -1.9": ["discriminatory"], "7.6 4.1 10.2": ["plumbing"], "-1.2 13.7 2.9": ["toughness"], "1.9 19.7 2.9": ["provoke"], "3.0 12.4 9.2": ["eroded"], "-0.1 1.6 9.0": ["wrestled"], "24.5 -3.7 1.4": ["unveils"], "3.5 21.0 8.9": ["cruelty"], "13.7 3.2 6.2": ["muted"], "5.1 -0.5 0.3": ["compression"], "3.2 3.4 10.1": ["bicycles"], "13.3 2.1 -4.2": ["redesigned"], "3.4 -1.2 -5.3": ["inundated"], "-10.8 6.3 -1.5": ["writings"], "6.9 8.4 3.1": ["extracted"], "4.9 16.5 8.7": ["kissing"], "8.2 6.8 7.0": ["vivid"], "5.6 2.2 1.4": ["interfaces"], "-1.2 -0.8 4.5": ["teleconference"], "8.5 9.8 7.2": ["altering"], "5.9 11.7 3.3": ["defiant"], "4.2 7.4 7.7": ["groundwork"], "1.3 9.7 1.3": ["airlifted"], "6.7 6.5 1.3": ["desks"], "9.9 7.0 0.3": ["modernize"], "14.3 18.6 9.7": ["plague"], "11.5 9.6 5.8": ["manually"], "0.5 2.2 2.7": ["stitches"], "26.5 2.3 7.8": ["resembles"], "3.5 9.2 -8.0": ["condemning"], "15.4 9.8 13.1": ["spills"], "14.4 12.4 6.2": ["dismantling"], "10.5 -2.6 4.5": ["simplified"], "3.6 10.5 8.0": ["frustrations"], "0.5 7.3 2.6": ["outshot"], "10.4 9.4 10.9": ["extraction"], "-5.4 12.4 10.4": ["borrower"], "21.6 17.1 5.1": ["sphere"], "0.9 6.2 5.3": ["sunglasses"], "15.3 24.1 24.1": ["traps"], "2.5 10.7 11.8": ["levees", "operand"], "15.8 4.9 10.9": ["clusters"], "19.2 10.2 11.9": ["crumbling"], "9.9 11.4 37.7": ["shoreline"], "14.1 3.8 2.3": ["propel"], "-2.4 2.6 12.6": ["varies"], "10.6 6.3 17.1": ["nightly"], "9.2 1.2 21.9": ["canned"], "3.7 11.3 11.7": ["slopes"], "2.2 22.2 5.7": ["ignorant"], "3.5 19.1 13.0": ["calculating"], "6.4 26.9 8.4": ["deception"], "7.2 2.6 1.0": ["emulate"], "-1.6 10.7 6.7": ["accumulation"], "14.1 14.7 23.4": ["nest"], "-3.9 -0.8 0.8": ["qualifies"], "0.2 6.7 0.9": ["tweets"], "10.5 7.8 -4.7": ["visionary"], "7.3 2.6 11.8": ["footed"], "13.1 26.6 4.5": ["thugs"], "2.5 12.8 0.6": ["chants"], "6.6 5.9 10.7": ["tick"], "7.1 9.1 5.7": ["pat"], "9.4 0.5 27.1": ["baked"], "3.2 6.2 16.6": ["biomass"], "5.1 8.0 10.2": ["racer"], "8.5 2.8 7.7": ["hamper"], "1.8 9.4 11.5": ["f"], "-8.1 -0.5 6.0": ["departures"], "4.2 2.6 1.5": ["fashionable"], "-5.1 1.0 17.4": ["condos"], "10.8 -0.1 3.7": ["unsuccessfully"], "14.4 1.9 5.3": ["plowed"], "3.3 24.6 8.5": ["unarmed"], "8.1 -0.1 7.1": ["maturing"], "6.2 1.3 3.1": ["hopefuls"], "8.7 11.6 13.7": ["submerged"], "11.9 8.7 2.8": ["improbable"], "22.7 15.7 29.5": ["rat"], "6.3 -1.8 4.3": ["voucher"], "7.9 7.4 11.3": ["disbelief"], "3.1 -1.8 6.1": ["vetoed"], "11.4 -7.4 4.1": ["culminated"], "0.5 29.5 5.1": ["oppression"], "-4.3 14.6 4.2": ["misunderstanding"], "29.1 16.2 8.6": ["exploding"], "-4.1 -1.1 2.4": ["hectic"], "-0.4 5.8 -2.0": ["fostering"], "18.1 2.6 5.7": ["sparkling"], "6.6 -2.2 8.2": ["skipping"], "0.3 3.4 16.6": ["parishes"], "-3.7 0.1 8.1": ["remodeling"], "20.0 16.3 16.2": ["combo"], "9.5 0.8 1.8": ["uproar"], "2.4 0.5 6.4": ["adolescents"], "4.0 10.7 3.0": ["succumbed"], "3.4 10.7 12.0": ["mouths"], "19.7 -2.2 4.9": ["windfall"], "14.0 9.0 7.7": ["tempting"], "-0.3 14.2 8.2": ["graves"], "2.7 10.1 10.9": ["campers"], "-5.4 4.9 9.8": ["wardrobe"], "-2.9 0.0 -0.1": ["scalability"], "-6.8 8.7 -9.4": ["empowering"], "-7.0 0.3 3.3": ["affordability"], "8.6 9.0 -0.7": ["ceased"], "-1.8 12.1 0.8": ["deed"], "2.0 5.3 8.3": ["tissues"], "18.3 3.1 13.1": ["buyback"], "9.7 17.1 17.5": ["shit"], "10.1 8.3 19.3": ["pounder"], "9.4 5.8 -2.7": ["reassuring"], "6.6 9.9 5.9": ["disrupting"], "7.5 5.6 5.2": ["guardian"], "10.0 7.5 12.2": ["unsustainable"], "4.4 4.5 19.6": ["cottage"], "4.7 15.5 11.9": ["wedge"], "2.0 12.3 23.4": ["waterways"], "9.4 4.5 17.4": ["dipping"], "6.0 11.7 -0.5": ["knocks"], "2.4 -0.2 10.7": ["resuming"], "13.0 5.2 9.0": ["warehouses"], "4.3 12.2 2.4": ["haunt"], "-1.7 8.1 4.1": ["diarrhea"], "12.7 10.1 5.2": ["doorstep"], "9.2 5.9 7.7": ["untouched"], "1.3 -7.6 5.1": ["hiatus"], "10.3 14.7 41.2": ["sharks"], "0.8 17.4 0.5": ["mobilized"], "-3.4 21.5 0.8": ["informant"], "1.0 9.1 2.6": ["wards"], "6.8 22.7 8.3": ["arrogance"], "7.6 0.8 -3.3": ["scanner"], "4.6 7.7 0.8": ["pathway"], "11.7 4.8 7.9": ["fusion"], "12.3 7.6 5.6": ["lifeline"], "9.7 10.9 12.3": ["screw"], "10.5 6.0 2.0": ["quiz"], "9.8 22.7 8.2": ["entrenched"], "10.5 -1.4 1.8": ["feasibility"], "6.2 12.7 2.6": ["greeting"], "3.6 14.1 6.5": ["conceding"], "5.0 1.1 12.2": ["surcharge"], "-0.2 -4.8 23.8": ["lunches"], "18.5 7.7 9.3": ["climbs"], "9.9 -1.8 6.9": ["unfolded"], "12.2 11.3 2.6": ["exiting"], "2.1 11.6 4.0": ["annoyed"], "4.7 21.6 3.2": ["unpleasant"], "-0.3 6.2 7.9": ["progresses"], "8.5 3.5 14.1": ["curling"], "23.0 0.2 3.6": ["likened"], "14.2 0.7 7.0": ["textiles"], "-4.0 14.9 9.8": ["roadways"], "6.3 0.0 0.6": ["limelight"], "5.4 20.3 10.0": ["stubborn"], "16.4 30.4 6.7": ["mankind"], "5.4 16.2 0.3": ["endanger"], "2.8 19.1 -0.2": ["faults"], "3.7 11.3 9.3": ["darker"], "17.4 11.8 1.9": ["roared"], "10.3 12.1 13.7": ["stagnant"], "7.8 14.4 1.6": ["freeing"], "18.2 4.3 0.3": ["littered"], "9.7 7.2 1.0": ["plugged"], "2.6 10.8 1.2": ["disclosing"], "5.1 7.3 2.9": ["comparative"], "-10.2 -1.5 1.0": ["essays"], "6.7 -3.7 0.6": ["finalizing"], "15.5 14.0 10.1": ["gadget"], "18.8 9.3 8.2": ["tame"], "4.4 2.3 3.5": ["bookstore"], "0.9 7.4 -2.6": ["mediator"], "10.6 10.0 -0.4": ["turbulence"], "-6.4 4.9 3.0": ["articulate"], "17.6 10.8 5.7": ["sucked"], "0.6 1.2 12.9": ["sitcom"], "8.2 7.0 14.8": ["decorations"], "8.5 1.7 10.7": ["sketch"], "-6.1 15.2 4.9": ["replies"], "18.8 16.9 7.9": ["simulated"], "14.5 1.5 -3.2": ["taps"], "-5.1 4.1 1.2": ["timeframe"], "3.9 4.6 4.6": ["entertainer"], "6.8 3.4 25.6": ["fur"], "9.9 5.6 9.4": ["decidedly"], "6.0 21.8 4.5": ["unilateral"], "20.8 11.3 17.0": ["princess"], "3.7 9.2 3.7": ["forging"], "-1.8 0.9 0.9": ["unresolved"], "10.1 15.6 7.0": ["disgusting"], "9.8 6.2 13.2": ["delightful"], "10.1 15.8 1.1": ["kidnap"], "0.6 22.3 2.2": ["brutality"], "2.0 2.8 0.9": ["issuers"], "3.3 -2.0 -4.1": ["noteworthy"], "15.4 16.8 6.0": ["horizontal"], "8.0 7.3 16.1": ["offspring"], "14.3 2.3 7.6": ["schoolchildren"], "19.8 -2.8 -2.3": ["bln"], "15.6 11.8 8.6": ["guessed"], "7.1 0.7 -1.2": ["tumultuous"], "0.2 -1.9 2.6": ["journals"], "17.2 4.8 3.3": ["boon"], "12.3 4.7 18.3": ["pale"], "16.7 9.7 13.4": ["doom"], "21.2 3.9 6.3": ["storied"], "5.3 5.1 12.3": ["tattoos"], "5.8 24.0 7.9": ["disguise"], "6.2 13.6 7.9": ["stockpiles"], "-9.9 6.6 14.2": ["schooling"], "-3.1 3.3 8.0": ["fabrics"], "8.2 29.4 5.2": ["ruthless"], "8.2 23.5 4.6": ["intimidate"], "-5.4 6.7 14.0": ["groundwater"], "2.0 5.1 4.8": ["sleeves"], "5.3 3.8 2.1": ["informational"], "6.2 11.8 5.6": ["hierarchy"], "5.5 0.8 3.2": ["cosmetic"], "14.0 12.5 11.9": ["cue"], "-2.3 -0.9 0.3": ["lifestyles"], "9.9 13.7 8.1": ["classmate"], "15.1 3.9 1.3": ["campaigners"], "11.0 8.5 -0.8": ["pervasive"], "8.5 10.9 6.6": ["dreaming"], "-0.2 15.1 7.3": ["hardcore"], "17.8 4.8 17.9": ["fest"], "19.5 5.7 10.1": ["severed"], "8.5 6.7 9.3": ["uneven"], "5.3 2.3 2.1": ["strangled"], "13.8 8.7 30.2": ["buffet"], "5.3 9.1 1.6": ["smuggled"], "1.3 -1.1 4.3": ["fuss"], "2.7 5.9 -0.7": ["avid"], "-4.3 7.6 7.3": ["commuter"], "2.5 9.8 8.8": ["discontent"], "3.6 12.4 1.8": ["undervalued"], "16.3 3.4 7.1": ["gloomy"], "14.6 7.5 14.4": ["palm"], "-1.6 11.0 7.2": ["philosophical"], "-6.8 9.7 5.7": ["demeanor"], "2.4 6.1 1.9": ["suicides"], "-1.6 -0.7 1.6": ["auditions"], "3.7 3.2 6.7": ["curtail"], "0.9 17.4 6.9": ["minimizing"], "13.7 -2.2 3.0": ["entice"], "19.9 13.3 5.5": ["breathtaking"], "2.6 4.8 34.2": ["steak"], "-6.7 6.8 11.5": ["budgetary"], "11.3 4.9 11.6": ["joints"], "3.4 6.1 4.1": ["lapse"], "8.0 5.4 -4.7": ["praises"], "11.8 26.4 10.9": ["illusion"], "1.9 7.4 13.9": ["quarantine"], "0.5 -3.2 5.3": ["gigs"], "3.6 13.6 25.1": ["peninsula"], "-0.4 18.4 3.6": ["repression"], "-2.9 -0.3 -2.1": ["facilitated"], "11.6 1.6 2.1": ["quits"], "10.3 8.3 8.5": ["muddy"], "15.5 9.0 4.6": ["govt"], "0.3 11.9 7.7": ["variables"], "7.0 12.9 9.7": ["reset"], "3.9 14.0 11.4": ["liking"], "-1.9 12.9 14.5": ["vest"], "6.4 9.6 2.7": ["cache"], "0.6 13.6 12.7": ["pollutants"], "9.3 5.9 13.1": ["spikes"], "15.9 10.9 11.3": ["doll"], "-4.3 4.1 15.7": ["novice"], "0.5 13.5 3.1": ["stigma"], "5.8 12.9 13.2": ["triggers"], "12.3 10.9 10.7": ["props"], "10.9 7.4 6.2": ["projecting"], "9.0 -0.5 5.6": ["specialize"], "14.6 15.2 11.8": ["sideways"], "5.6 10.5 6.7": ["rails"], "-4.1 4.4 6.5": ["disparity"], "7.5 17.0 4.5": ["conceal"], "6.2 9.9 3.4": ["blackout"], "6.8 8.0 46.8": ["tomato"], "3.5 7.7 -2.7": ["defamation"], "14.9 -0.5 15.0": ["skinny"], "11.8 18.9 4.0": ["duel"], "29.2 8.1 3.3": ["retailing"], "14.3 6.1 10.7": ["lamp"], "12.6 9.1 -4.9": ["innovator"], "-6.9 5.9 0.8": ["formulation"], "14.0 16.5 10.1": ["fury"], "19.2 17.0 14.8": ["heaviest"], "-6.6 21.7 1.7": ["persecution"], "9.3 6.0 15.6": ["funk"], "15.5 13.3 15.1": ["melted"], "18.6 6.2 7.2": ["rocking"], "4.4 8.4 1.7": ["pitted"], "7.2 14.1 0.6": ["downfall"], "2.0 3.8 6.7": ["moderately"], "13.9 30.9 5.5": ["menace"], "4.1 -3.2 2.1": ["contractual"], "-4.1 6.7 3.8": ["songwriter"], "1.9 -7.8 -4.3": ["stints"], "2.5 13.4 5.2": ["windy"], "3.2 14.7 -0.7": ["forgiven"], "10.5 1.6 9.0": ["pesos"], "3.7 -2.4 -3.9": ["championed"], "2.9 6.9 7.1": ["exacerbated"], "17.2 9.9 0.7": ["obscene"], "0.4 9.8 7.9": ["disposition"], "0.7 5.6 9.2": ["vibe"], "-4.3 9.1 4.0": ["fracture"], "9.7 4.9 11.9": ["trimming"], "10.9 -1.2 -4.0": ["redesign"], "5.6 8.2 36.9": ["garlic"], "5.7 9.4 17.6": ["patio"], "-4.4 8.9 -5.0": ["excerpts"], "-1.3 5.3 14.8": ["selectmen"], "-1.8 3.3 2.3": ["entrepreneurship"], "14.0 8.9 7.5": ["bash"], "8.0 13.0 8.8": ["terminology"], "6.8 14.6 20.8": ["foil"], "-4.7 -0.1 1.4": ["presiding"], "7.3 9.1 5.2": ["populist"], "9.8 12.2 12.5": ["stern"], "-4.8 21.6 -1.0": ["operative"], "2.9 3.9 28.4": ["marina"], "-6.8 5.1 2.6": ["unearned"], "-3.4 6.5 13.4": ["homelessness"], "-1.4 6.2 2.0": ["therapist"], "19.0 3.4 9.4": ["shrank"], "1.4 -0.3 7.3": ["grading", "cern"], "4.8 22.8 7.3": ["culprits"], "4.0 2.5 12.3": ["clerks"], "10.4 8.2 2.2": ["fascinated"], "-4.1 10.0 2.6": ["factual"], "0.5 18.0 9.6": ["captivity"], "0.8 13.0 -3.0": ["detrimental"], "2.0 10.5 2.6": ["avoids"], "18.5 21.6 20.9": ["castle"], "9.9 11.6 5.0": ["populated"], "-0.0 8.0 1.1": ["separates"], "20.1 0.3 17.7": ["coated"], "-0.3 7.4 5.6": ["jumpers"], "-4.4 5.5 -0.0": ["contesting"], "2.2 6.2 5.2": ["complying"], "0.1 13.7 -1.1": ["endangering"], "14.1 7.3 8.9": ["spat"], "19.5 -4.2 -0.9": ["touting"], "8.9 13.2 8.9": ["disproportionate"], "9.9 13.9 10.2": ["agility"], "8.5 13.5 22.9": ["tooth"], "16.6 17.9 6.3": ["pillars"], "6.0 13.2 11.1": ["forehand"], "0.7 5.8 -5.7": ["thanking"], "1.5 2.4 -5.4": ["reinforces"], "6.3 3.2 6.3": ["automate"], "9.9 9.4 22.3": ["cookie"], "1.1 32.2 2.9": ["battalion"], "-3.9 9.8 9.5": ["tolls"], "11.7 -1.3 16.4": ["lunchtime"], "8.4 -0.1 0.0": ["legality"], "16.2 7.3 -2.0": ["synonymous"], "-0.7 5.5 4.0": ["routines"], "17.8 6.9 0.3": ["hoax"], "12.2 -4.0 0.3": ["subsidize"], "2.7 19.6 5.4": ["dislike"], "-8.2 10.0 0.5": ["expulsion"], "-3.4 11.2 9.4": ["abdomen"], "4.3 15.5 7.3": ["filibuster"], "2.1 -6.6 5.1": ["registrations"], "-2.6 2.9 -3.6": ["strives"], "0.2 20.0 5.5": ["barracks"], "-0.4 9.6 14.1": ["reservoirs"], "8.2 27.6 7.6": ["idiot"], "10.4 0.5 -1.2": ["embroiled"], "7.9 7.9 1.5": ["louder"], "2.9 6.5 6.6": ["humorous"], "6.7 10.0 10.6": ["quipped"], "-2.8 9.0 0.1": ["assign"], "27.2 9.2 5.0": ["monumental"], "-6.8 24.7 0.9": ["honorable"], "8.0 15.2 1.4": ["distract"], "12.2 7.6 18.4": ["melting"], "-1.1 18.3 10.6": ["disarmament"], "-0.3 6.5 3.6": ["compiling"], "-0.5 14.8 4.1": ["statistic"], "11.8 6.3 10.2": ["horns"], "0.5 -3.1 18.8": ["coats"], "7.6 1.3 -2.8": ["spacious"], "8.8 6.1 26.4": ["barge"], "1.4 3.7 2.6": ["activation"], "4.0 7.3 3.5": ["homage"], "10.3 11.0 13.8": ["choking"], "1.0 -0.0 3.4": ["documentaries"], "7.0 9.1 6.9": ["paints"], "10.5 18.4 4.6": ["carnage"], "15.4 -3.0 8.0": ["y"], "26.3 3.8 10.6": ["heavyweights"], "18.1 11.4 7.9": ["depicts", "lifelogging"], "2.6 6.2 1.4": ["cough"], "6.5 12.6 4.0": ["attachment"], "2.8 8.7 6.2": ["shaft"], "14.1 0.3 5.2": ["laced"], "9.4 8.8 3.0": ["pressuring"], "1.1 12.7 5.5": ["forehead"], "9.5 15.5 6.9": ["persona"], "11.9 4.2 11.4": ["rocker"], "-3.6 4.5 -0.6": ["conversions"], "5.1 6.2 0.7": ["sleeve"], "8.5 14.6 11.6": ["landscapes"], "6.3 7.2 3.3": ["r"], "10.6 14.5 9.9": ["buffer"], "8.5 9.1 8.7": ["disperse"], "17.4 21.8 11.4": ["puppet"], "6.4 10.9 6.7": ["collisions"], "3.9 0.9 13.0": ["stamps"], "7.6 12.3 12.2": ["lesbians"], "6.8 14.5 5.6": ["vow"], "12.8 2.6 7.3": ["reviving"], "-4.0 1.6 4.6": ["defer"], "11.3 10.0 -7.6": ["dusty"], "1.5 0.6 -6.3": ["congratulations"], "-4.8 3.8 2.6": ["oncology"], "17.9 4.6 5.3": ["bursting"], "4.4 14.0 -0.9": ["humbled"], "12.2 17.1 5.1": ["dreadful"], "0.0 9.5 2.3": ["dialing"], "-0.7 0.1 11.7": ["gown"], "-0.8 12.2 -1.9": ["paramount"], "6.2 17.1 4.9": ["disgrace"], "2.7 32.0 -0.9": ["jihad"], "5.0 14.9 8.2": ["consequently", "stero"], "3.9 18.9 2.5": ["surrendering"], "6.5 9.0 1.4": ["swaps"], "-2.5 11.3 6.7": ["bind"], "18.1 17.0 31.3": ["worms"], "-0.3 2.5 7.7": ["underage"], "8.6 1.8 27.2": ["freezer"], "6.0 14.5 1.4": ["inefficient"], "10.7 10.4 11.8": ["token"], "7.4 1.1 21.7": ["dough"], "6.7 -3.0 10.8": ["packets"], "17.1 21.3 12.1": ["ruler"], "12.8 -4.5 8.7": ["scooped"], "16.8 2.3 -2.1": ["gainers"], "7.3 8.4 2.3": ["envision"], "5.9 13.4 10.9": ["speculators"], "21.6 13.8 4.9": ["ominous"], "9.5 8.9 4.5": ["breakup"], "-4.4 1.6 3.5": ["relaxation"], "8.5 17.2 9.3": ["grin"], "2.5 16.4 11.3": ["blessings"], "-6.3 2.4 -7.2": ["listens"], "3.2 3.7 -4.2": ["auditing"], "11.7 14.6 6.6": ["mayhem"], "13.5 11.6 35.3": ["algae"], "8.4 11.5 7.2": ["bitten"], "8.5 5.3 6.7": ["eruption", "diameters"], "10.0 17.1 4.1": ["secretive"], "3.4 25.6 5.7": ["servicemen"], "5.5 13.3 9.2": ["stray"], "17.7 7.0 14.3": ["sticky"], "1.6 18.8 17.7": ["dwelling"], "2.1 7.6 3.7": ["conducive"], "9.5 12.1 6.5": ["fond"], "2.6 6.2 -2.3": ["liquids"], "4.5 18.9 7.7": ["mountainous"], "-1.1 4.2 -2.0": ["appreciative"], "6.9 7.5 18.0": ["baking"], "7.4 5.5 4.7": ["showroom"], "24.4 3.2 5.5": ["sizeable"], "6.4 1.2 4.5": ["renewing"], "-5.3 9.3 6.0": ["nonpartisan"], "7.3 7.8 -0.0": ["echo"], "9.3 12.9 12.8": ["scenery"], "-5.8 5.0 10.0": ["budgeting"], "0.1 29.2 9.0": ["disarm"], "15.7 3.3 18.8": ["mesh"], "1.2 8.2 1.0": ["alarms"], "4.4 8.9 10.2": ["geological"], "8.0 3.3 0.2": ["streamed"], "-4.4 3.5 1.8": ["compilation"], "5.4 11.3 11.4": ["takeoff"], "2.6 7.3 1.2": ["dont"], "-7.1 0.7 5.8": ["westbound"], "17.7 6.6 15.2": ["dome"], "0.2 7.5 -0.6": ["inspires"], "0.3 5.5 2.1": ["deductions"], "-0.2 14.1 3.8": ["annexation"], "1.2 -8.2 3.9": ["syndicated"], "12.9 -1.4 5.4": ["ticked"], "6.3 8.0 6.6": ["passwords"], "11.1 -5.5 6.3": ["com"], "3.2 1.3 1.1": ["favorably"], "-6.6 -6.4 8.4": ["salon"], "10.6 3.9 17.6": ["cereal"], "9.5 14.8 16.3": ["bureaucratic"], "12.6 10.2 4.4": ["consulate"], "11.9 8.7 5.1": ["greats"], "-2.6 7.8 7.5": ["relievers"], "14.3 8.5 19.6": ["coating"], "-7.3 5.1 6.3": ["bassist"], "3.7 7.4 7.3": ["councilman"], "-1.1 2.0 -1.3": ["forgery"], "22.4 10.6 12.8": ["glow"], "3.1 1.5 6.6": ["g"], "7.3 4.1 1.0": ["fliers"], "14.2 5.6 8.7": ["marvelous"], "18.6 4.9 1.9": ["hubs"], "7.0 3.1 3.0": ["orderly"], "17.0 6.4 4.9": ["computerized"], "4.1 14.9 15.7": ["treasures"], "-5.2 8.6 2.3": ["constrained"], "21.7 3.0 5.4": ["millionaire"], "16.0 -2.6 7.6": ["settles"], "0.2 23.5 13.7": ["instincts"], "7.6 4.1 10.5": ["spoil"], "10.8 1.9 6.7": ["standstill"], "6.4 21.3 7.1": ["presumed"], "-1.5 1.5 7.0": ["dramas"], "6.7 8.1 11.2": ["thereof"], "4.0 6.3 2.0": ["shortest"], "8.2 3.1 2.6": ["booster"], "-7.9 9.7 25.5": ["boating"], "1.7 7.7 8.7": ["repertoire"], "3.7 -0.2 1.6": ["exhibiting"], "-2.4 5.8 3.4": ["deteriorate"], "7.4 17.8 5.5": ["pullout"], "16.5 16.8 4.8": ["roar"], "47.9 1.6 15.1": ["mammoth"], "0.5 14.6 6.6": ["multilateral"], "5.2 1.7 4.8": ["plead"], "10.5 -4.1 4.6": ["curbs"], "20.3 1.4 -2.5": ["pioneers"], "4.3 2.4 10.7": ["fetus"], "-3.3 0.9 -0.7": ["phoned"], "-11.4 6.3 5.6": ["playwright"], "13.1 22.9 7.4": ["apparatus"], "4.8 5.0 -3.0": ["securely"], "0.4 21.7 8.1": ["risking"], "6.1 8.7 8.7": ["soften", "lad"], "12.7 9.8 0.9": ["blistering"], "-1.2 19.6 5.3": ["rifles"], "7.9 -1.4 -2.9": ["booted"], "9.9 25.4 0.3": ["espionage"], "1.2 7.1 20.7": ["voyage"], "3.4 8.7 6.0": ["landfall"], "1.4 7.9 5.0": ["accumulate"], "-0.4 -0.5 -4.9": ["validated"], "-4.5 3.8 7.0": ["eastbound"], "59.9 13.3 14.9": ["gigantic"], "21.1 1.7 -5.9": ["plc"], "3.0 9.2 5.1": ["splits"], "-0.7 0.0 -4.7": ["questionnaire"], "15.0 5.4 0.2": ["hacked"], "-3.9 11.6 12.1": ["percentages"], "-5.7 9.8 0.3": ["autobiography"], "5.2 7.9 7.2": ["retrieved"], "9.7 -1.9 16.7": ["shaved"], "3.6 5.0 15.3": ["oz"], "-1.2 -1.6 -1.8": ["validate"], "2.9 17.0 5.4": ["risked"], "11.7 13.0 1.4": ["programmed"], "-4.3 1.0 14.7": ["diets"], "0.9 1.2 2.1": ["retires"], "4.7 9.4 14.6": ["vets"], "-2.6 -0.6 0.8": ["collaborations"], "-7.0 5.1 1.8": ["felonies"], "8.3 -3.2 1.3": ["reimburse"], "-0.4 -2.7 1.3": ["commissioning"], "4.7 15.0 8.4": ["pity"], "11.1 7.7 7.9": ["scratching"], "-4.6 4.4 -2.1": ["pertinent"], "23.6 6.0 11.2": ["faltering"], "5.5 1.8 7.0": ["methane"], "15.5 5.5 16.7": ["meager"], "14.3 8.5 6.3": ["visions"], "3.9 6.9 1.0": ["copying"], "5.9 2.9 1.3": ["levied"], "16.2 15.1 1.9": ["pillar"], "11.9 13.6 3.0": ["chilling"], "-1.9 5.0 11.1": ["taping"], "0.2 12.1 1.9": ["kidnappings"], "13.0 2.4 -0.3": ["underscore"], "1.6 6.0 3.4": ["indictments"], "8.7 6.7 4.2": ["undertakes"], "10.3 23.6 7.3": ["hates"], "-1.0 -0.5 2.0": ["tendered"], "1.4 9.4 14.1": ["tasted"], "5.6 8.4 8.6": ["panicked"], "0.1 13.2 0.7": ["maximizing"], "17.7 0.4 15.8": ["fork"], "0.8 17.6 5.4": ["nationality"], "7.8 4.7 5.2": ["syndicate"], "-1.5 -4.5 2.5": ["reimbursed"], "9.4 -1.4 8.5": ["sickened"], "-0.3 -5.7 -2.4": ["postponement"], "0.5 9.6 6.3": ["fumbles"], "7.7 6.4 1.1": ["twists"], "11.7 16.6 9.8": ["randomly"], "6.1 4.5 3.2": ["rewrite"], "9.1 5.9 2.4": ["bondholders"], "9.3 15.0 1.7": ["flashes"], "6.1 8.5 1.4": ["authorizing"], "9.9 20.6 5.7": ["horrendous"], "10.6 2.4 5.9": ["upheaval"], "3.8 4.0 4.2": ["configurations"], "19.9 14.5 12.4": ["greedy"], "5.2 4.6 7.2": ["curbing"], "12.5 -0.5 4.3": ["clinging"], "5.1 4.3 -0.8": ["enrich"], "-0.1 2.2 -4.0": ["durability"], "24.2 -0.1 10.7": ["spiraling"], "7.2 14.0 7.3": ["stereotypes"], "6.7 -7.2 2.9": ["spanned"], "2.8 1.4 2.3": ["injections"], "9.8 20.9 12.4": ["shelling"], "5.3 5.1 4.0": ["cyclist"], "10.8 10.8 10.8": ["medieval"], "18.9 20.2 23.2": ["snakes"], "-5.5 10.5 -2.0": ["preaching"], "17.6 13.3 6.8": ["vowing"], "8.0 13.4 12.4": ["kinda"], "18.4 2.8 6.8": ["eur"], "15.5 8.8 0.6": ["dismantled"], "5.6 2.3 4.0": ["trickle"], "9.0 14.6 3.9": ["screams"], "3.2 0.2 21.9": ["spice"], "11.5 6.3 2.5": ["aids"], "8.5 2.6 14.0": ["racetrack"], "0.0 0.1 9.4": ["clientele"], "17.0 9.3 17.7": ["popcorn"], "6.9 21.7 14.3": ["smugglers"], "-4.7 3.5 1.8": ["backups"], "2.8 5.3 4.3": ["withhold"], "2.2 6.5 7.9": ["prostitute"], "0.7 9.7 6.1": ["dictated"], "11.0 12.4 11.3": ["envy"], "6.8 11.1 2.3": ["rained"], "1.3 18.4 -0.9": ["combating"], "-4.0 15.5 9.9": ["moderates"], "10.2 11.1 12.1": ["rub"], "-3.6 9.0 28.5": ["herbs"], "8.0 1.4 0.0": ["flowed"], "-0.6 6.6 6.0": ["pilgrimage"], "1.6 9.1 6.2": ["torque"], "-6.2 2.6 -4.1": ["induction"], "5.0 11.2 6.0": ["allergies"], "2.6 14.0 3.1": ["energized"], "4.1 8.5 6.3": ["dysfunctional"], "-0.3 5.6 3.1": ["statutes"], "-5.2 2.6 4.2": ["actresses"], "5.2 10.6 7.6": ["downstairs"], "13.5 2.3 12.6": ["pristine"], "6.8 25.5 4.3": ["posture"], "11.6 6.1 5.0": ["stripping"], "1.8 2.0 5.0": ["respite"], "1.0 7.3 0.3": ["rejoin"], "7.3 4.3 0.1": ["relocating"], "-4.7 13.5 13.3": ["petty"], "6.3 7.6 4.4": ["worrisome"], "5.7 1.8 12.4": ["oils"], "2.3 17.0 20.3": ["cruiser"], "3.1 2.8 13.4": ["hormones"], "-0.4 20.1 9.4": ["jealous"], "16.7 3.9 -0.4": ["buzzing"], "9.1 -1.8 0.3": ["downplayed"], "-7.7 -0.2 8.7": ["inflows"], "3.4 2.3 9.3": ["furnishings"], "-3.2 19.3 9.3": ["lawful"], "10.9 10.4 19.0": ["drifting"], "0.9 7.8 2.4": ["foresee"], "-0.6 10.5 6.2": ["imbalance"], "-1.9 25.5 5.4": ["commanded"], "8.9 7.9 3.1": ["turbine"], "11.4 11.7 1.4": ["troublesome"], "13.8 18.8 9.4": ["pals"], "-2.8 0.1 4.6": ["podcast"], "12.5 6.4 10.7": ["drunken"], "2.7 8.6 3.5": ["tweet"], "-0.8 2.0 -0.1": ["stimulating"], "-11.2 3.8 3.4": ["instructional"], "3.3 1.8 5.7": ["invalid"], "11.9 -1.7 5.0": ["culminating"], "2.2 7.7 5.9": ["measurable"], "9.2 7.8 1.5": ["gentlemen"], "5.6 17.7 0.2": ["flank"], "11.6 10.0 -3.6": ["radically"], "8.4 11.0 4.1": ["courtyard"], "-1.5 4.4 8.9": ["internationals"], "6.0 3.9 33.4": ["bacon"], "5.3 15.3 1.8": ["shameful"], "4.4 7.3 10.6": ["facial"], "3.0 15.3 4.3": ["fatality"], "9.6 22.4 12.0": ["divine"], "1.8 47.7 7.6": ["comrades"], "6.8 7.7 5.9": ["stroll"], "5.9 7.3 4.5": ["flare"], "13.8 3.0 14.7": ["ramps"], "14.1 17.4 8.0": ["stalking"], "11.7 7.5 0.5": ["incorrectly"], "10.7 24.1 0.5": ["systematically"], "26.0 13.5 4.9": ["roaring"], "18.2 5.2 -5.6": ["standalone"], "11.4 16.7 -0.1": ["underestimated"], "12.6 17.3 6.1": ["landmarks"], "2.1 8.2 7.7": ["marrying"], "2.2 1.4 8.4": ["regeneration"], "10.2 5.5 11.9": ["centimeters"], "7.9 -1.1 5.0": ["roundup"], "-1.3 3.2 -1.8": ["expresses"], "5.2 4.9 5.7": ["rounding"], "-1.7 9.6 -1.3": ["divisional"], "1.8 5.6 1.5": ["excelled"], "-5.3 12.9 3.7": ["friendships"], "13.2 30.0 15.4": ["bully"], "14.8 -0.9 -1.2": ["advent"], "4.1 6.2 11.6": ["graft"], "18.8 10.8 12.5": ["flattened"], "0.3 21.4 3.1": ["frontline"], "6.9 18.4 3.0": ["incapable"], "9.8 7.9 29.6": ["hog"], "16.3 3.1 3.7": ["homegrown"], "14.7 10.6 3.5": ["astounding"], "1.6 1.4 4.2": ["elevate"], "18.9 13.1 9.6": ["intricate"], "16.6 2.5 7.2": ["novelty"], "1.8 16.5 0.4": ["suppression"], "3.9 6.4 15.4": ["breasts"], "8.8 3.8 3.3": ["classy"], "0.7 0.1 2.6": ["histories"], "-0.0 10.9 6.5": ["burdens"], "18.1 6.3 14.4": ["spiral"], "10.2 1.7 12.0": ["stickers"], "14.6 7.6 9.0": ["phony"], "6.3 7.8 28.9": ["diners"], "-4.2 15.5 -2.4": ["unmarked"], "3.5 5.6 -0.5": ["reforming"], "7.2 8.8 6.1": ["stepfather"], "19.4 -6.7 13.8": ["pricey"], "8.7 11.0 10.2": ["cyclone"], "-4.5 6.4 2.0": ["mpg"], "4.5 -0.1 5.9": ["wallets"], "2.4 0.5 0.8": ["nabbed"], "4.5 8.2 7.8": ["fabricated"], "7.2 20.4 21.7": ["sailor"], "12.9 9.3 -2.8": ["converts"], "12.3 0.4 15.4": ["froze"], "3.3 14.0 8.2": ["strategists"], "0.4 0.6 -4.3": ["audited"], "3.1 30.6 12.2": ["multiplayer"], "2.0 9.6 5.3": ["premiership"], "15.1 -1.3 11.1": ["bustling"], "5.6 6.7 -3.2": ["unfounded"], "7.5 7.1 4.4": ["narrowing"], "13.5 -1.0 3.0": ["brushed"], "-2.7 9.9 0.4": ["regretted"], "5.0 10.5 15.9": ["towed"], "-2.8 1.5 -0.9": ["referenced"], "1.6 -1.0 10.6": ["dished"], "1.9 4.2 3.4": ["notwithstanding"], "8.7 9.2 5.5": ["juror"], "-3.7 3.7 3.4": ["equitable"], "8.1 10.0 8.6": ["floodwaters"], "6.0 9.0 4.8": ["disparate"], "12.4 6.3 6.4": ["loophole"], "5.9 2.1 2.4": ["guaranteeing"], "11.0 9.7 9.0": ["wagon"], "4.0 12.1 4.6": ["inbox"], "4.8 15.1 -0.3": ["adapting"], "-4.4 12.5 4.2": ["agendas"], "8.0 9.1 8.1": ["stripes"], "1.2 -2.4 23.2": ["grilled"], "6.8 5.8 6.9": ["digest"], "11.7 8.6 44.0": ["potato"], "-0.5 11.8 -3.0": ["utmost"], "2.4 3.1 3.8": ["handcuffs"], "10.0 -1.7 13.9": ["payouts"], "12.9 -2.3 7.3": ["tentatively"], "8.2 13.4 -0.1": ["obsolete"], "11.9 8.0 -2.6": ["scanned"], "-1.2 6.2 -0.2": ["differential"], "-4.0 10.8 2.4": ["candid"], "-0.9 4.4 2.9": ["apologies"], "6.6 9.0 14.3": ["monks", "yaba"], "-0.4 5.4 3.1": ["poignant"], "13.3 18.0 13.1": ["spit"], "5.6 0.4 1.1": ["doctorate"], "1.3 32.6 -0.9": ["covert"], "5.9 6.0 19.3": ["reproduction"], "4.2 2.8 4.5": ["blends"], "8.0 5.4 6.5": ["leaned"], "1.7 8.7 15.2": ["monsoon"], "10.7 20.9 8.8": ["paparazzi"], "-0.9 4.9 0.4": ["solicitor"], "4.1 2.8 6.9": ["linger"], "12.6 10.8 6.7": ["approximate"], "8.4 -2.9 1.5": ["intrigued"], "10.2 3.2 12.4": ["afloat"], "6.3 0.8 8.5": ["mixes"], "-3.7 12.5 4.0": ["evacuations"], "5.8 8.7 4.0": ["username"], "3.6 7.2 21.7": ["nitrogen"], "13.2 -3.4 10.1": ["fairs"], "16.3 11.6 12.2": ["paradise"], "-5.0 14.3 2.6": ["hardships"], "5.7 8.0 12.8": ["defy"], "20.6 6.9 6.7": ["spilling"], "9.8 -2.5 8.2": ["budding"], "-4.5 1.4 2.4": ["residing"], "10.3 4.8 7.7": ["starved"], "3.3 -1.7 -3.3": ["premiered"], "9.9 5.3 13.0": ["grappling"], "8.5 4.5 -1.8": ["echoes"], "-3.2 29.1 10.5": ["hostilities"], "11.4 10.4 10.5": ["slippery"], "4.0 6.5 12.1": ["fabrication"], "14.8 13.6 8.9": ["enclosed"], "0.0 16.3 3.6": ["medics"], "-2.7 5.7 7.1": ["groundout"], "-2.8 10.5 0.5": ["sermon"], "9.0 4.2 1.4": ["nanotechnology"], "12.5 16.4 5.6": ["deceptive"], "3.8 9.1 14.4": ["icing"], "6.5 8.1 6.4": ["stewards"], "-9.2 9.9 4.9": ["prioritize"], "12.4 -0.6 1.2": ["rife"], "4.1 4.1 2.7": ["caffeine"], "11.9 10.1 8.0": ["masterpiece"], "4.8 15.6 8.9": ["worshipers", "metasedimentary"], "-2.8 11.6 7.4": ["moderation"], "5.0 39.5 15.2": ["sniper"], "4.2 1.5 -1.3": ["reassured"], "8.2 7.2 14.7": ["plentiful"], "11.4 5.5 3.0": ["ticking"], "2.8 -0.7 3.0": ["calendars"], "-2.6 2.2 0.8": ["deposition"], "12.9 13.3 6.6": ["marches"], "14.6 7.5 6.0": ["dolls"], "5.6 -2.1 3.2": ["brochure"], "10.2 3.8 13.6": ["decorating"], "2.7 9.9 8.8": ["ok"], "0.1 5.8 5.6": ["distraught"], "1.3 8.6 5.4": ["outrebounded"], "6.8 1.7 21.6": ["stocking"], "5.8 1.5 4.8": ["chic"], "6.6 14.8 3.2": ["confuse"], "13.8 15.6 32.8": ["wolf"], "-10.5 1.3 12.6": ["allocations"], "-10.7 -2.1 2.8": ["monies"], "11.8 11.2 5.3": ["havoc"], "4.8 3.2 13.8": ["hormone"], "10.8 7.9 2.4": ["linear"], "0.3 9.0 4.5": ["wed"], "8.7 6.8 5.2": ["grips"], "13.1 4.3 10.2": ["mural"], "11.5 5.2 4.2": ["jitters"], "5.4 7.7 4.3": ["sharper"], "0.0 10.2 12.1": ["ranchers"], "-7.2 4.4 4.0": ["outpatient"], "-2.4 3.8 2.0": ["previews"], "6.1 4.6 5.9": ["orphans"], "13.7 3.6 4.5": ["encompassing"], "-11.7 -2.7 4.6": ["referrals"], "-1.0 0.3 39.0": ["lamb"], "6.1 10.2 2.6": ["lineman"], "-1.3 6.3 2.3": ["cognitive"], "7.6 10.9 6.2": ["nonstop"], "12.8 2.7 2.7": ["woo"], "3.9 8.4 4.1": ["punter"], "18.1 3.7 10.5": ["tangled"], "15.1 6.7 9.1": ["superstars"], "-8.1 9.5 3.8": ["homicides"], "9.6 12.7 -0.8": ["autonomous"], "26.0 2.6 16.7": ["floats"], "8.9 -2.3 0.2": ["dampen"], "9.2 -1.6 11.9": ["ribbon"], "-1.6 12.6 4.0": ["meditation"], "9.4 5.1 12.4": ["charred"], "17.1 33.0 17.0": ["aliens"], "2.4 12.6 14.1": ["windshield"], "15.4 4.2 2.3": ["boasting"], "3.4 1.5 5.3": ["estates"], "1.2 5.1 18.3": ["skaters"], "2.9 -3.4 -1.0": ["supervise"], "6.5 13.5 -3.2": ["portraying"], "-10.0 4.9 -2.0": ["clinicians"], "-5.5 9.1 -1.5": ["asserts"], "9.0 4.0 2.2": ["revitalize"], "5.8 8.6 31.4": ["pots"], "17.7 10.8 9.3": ["bubbles"], "0.1 12.4 6.4": ["attic"], "7.0 13.3 15.0": ["knots"], "-3.4 9.6 6.5": ["intra"], "6.8 8.9 -1.2": ["enormously"], "8.8 11.6 7.5": ["notoriously"], "8.6 13.1 0.4": ["falsely"], "16.4 11.4 3.8": ["slamming"], "2.1 12.0 6.4": ["velocity"], "5.1 6.6 26.4": ["ponds"], "2.9 4.7 0.9": ["intern"], "-1.5 -3.8 4.2": ["reinstate"], "-5.9 7.4 2.5": ["pastors"], "3.3 4.0 10.8": ["timers"], "-13.6 9.4 4.5": ["incarcerated"], "5.0 17.1 16.1": ["territorial"], "6.7 8.9 0.5": ["ire"], "6.5 5.4 7.4": ["nostalgia"], "6.2 10.6 19.5": ["cane"], "7.0 3.7 2.0": ["accountants"], "14.8 34.5 -0.3": ["spies"], "5.9 9.6 7.0": ["insanity"], "6.8 14.2 11.3": ["cherished"], "3.9 19.4 6.0": ["hypocrisy"], "-2.0 11.4 19.5": ["breeds"], "13.4 11.4 7.4": ["benign"], "16.3 14.4 3.0": ["squarely"], "9.8 3.0 3.4": ["clipped"], "21.9 6.0 -1.1": ["inventor"], "9.2 9.4 7.2": ["shoved"], "9.0 -7.4 3.7": ["coincides"], "8.9 6.9 39.3": ["pier"], "-6.5 -1.0 2.7": ["expiring"], "27.7 22.0 15.7": ["gods"], "9.2 24.9 10.7": ["peril"], "-0.1 4.8 7.2": ["cricketers"], "7.0 13.7 -5.3": ["equip"], "9.1 10.9 7.6": ["gases"], "9.5 -2.5 0.7": ["fanfare"], "11.7 4.0 19.2": ["silk"], "2.7 0.1 3.9": ["tri"], "6.7 12.6 8.4": ["survives"], "19.7 19.1 15.5": ["goodness"], "3.2 7.1 0.5": ["manifesto"], "12.3 8.8 8.1": ["banging"], "4.5 2.9 4.4": ["megawatt"], "-10.5 0.6 6.4": ["resale"], "11.7 6.5 4.5": ["countdown"], "0.6 14.8 -0.0": ["infectious"], "0.4 5.0 6.0": ["interruption"], "12.8 7.9 -1.2": ["ignite"], "1.2 1.2 21.5": ["wool"], "6.0 22.3 3.2": ["destabilize"], "14.5 -2.5 6.4": ["swelled"], "-0.4 11.9 15.4": ["trackback"], "29.5 12.5 10.4": ["robotic"], "-6.9 0.7 -5.1": ["transcripts"], "6.1 19.1 -4.4": ["humiliating"], "7.8 7.6 11.3": ["adrift"], "26.6 8.7 6.8": ["glowing"], "11.7 25.3 7.1": ["eternal"], "1.9 15.0 10.6": ["whichever"], "-7.6 11.1 3.6": ["electing"], "-5.9 18.5 5.4": ["preparedness"], "-0.4 10.4 0.9": ["ventilation"], "9.1 16.4 -2.8": ["detecting"], "9.1 18.2 9.0": ["scent"], "-1.0 9.8 -5.0": ["diagnose"], "-3.1 4.8 21.5": ["bushel"], "7.4 5.7 5.2": ["underwriters"], "16.5 1.9 3.1": ["dotted"], "5.6 11.2 9.3": ["invasive"], "2.9 10.3 5.7": ["payback"], "4.2 16.2 7.7": ["harming"], "14.1 24.1 3.2": ["unleash"], "9.7 11.4 8.3": ["reluctantly"], "6.2 18.3 -0.9": ["underestimate"], "19.3 3.6 10.1": ["carve"], "15.7 8.6 -0.4": ["telecommunication"], "4.3 10.9 11.2": ["monarchy"], "3.6 12.0 4.4": ["boos"], "10.5 9.3 9.4": ["sibling"], "8.7 18.2 10.1": ["spraying"], "18.9 7.0 34.3": ["banana"], "13.2 4.7 4.2": ["lofty"], "19.4 2.1 9.0": ["weathered"], "-2.1 10.7 2.0": ["clerics"], "-5.5 17.4 4.6": ["attrition"], "5.5 10.8 11.6": ["flop"], "9.4 3.7 7.6": ["climax"], "3.3 6.2 5.9": ["forecasted"], "9.9 11.6 32.6": ["burger"], "2.8 8.5 11.2": ["depended"], "-5.5 6.3 -2.9": ["balloting"], "-4.2 7.7 2.7": ["synagogue"], "3.5 12.1 0.2": ["portrays"], "12.5 10.3 4.9": ["huddled"], "1.2 13.1 7.9": ["sporadic"], "15.4 16.4 1.5": ["absorbing"], "2.4 19.0 4.8": ["huddle", "oversimplifications"], "15.7 18.3 0.4": ["unthinkable"], "7.5 17.1 6.5": ["distorted"], "12.1 12.5 5.2": ["gruesome"], "-2.3 8.4 6.8": ["imposition"], "6.5 2.9 26.0": ["cakes"], "9.5 13.3 9.0": ["discovers"], "-1.5 0.6 3.4": ["expedite"], "7.1 21.1 6.4": ["eradicate"], "2.7 4.5 1.5": ["appalled"], "1.3 7.9 11.3": ["stove"], "4.1 4.2 4.0": ["streamlining"], "5.9 13.2 2.4": ["recruiter"], "9.3 7.7 5.7": ["breaching"], "-6.0 5.2 -1.5": ["infielder"], "8.0 5.9 5.6": ["precarious"], "-4.9 5.5 -0.5": ["attained"], "5.2 6.5 6.7": ["clicked"], "14.7 -4.8 3.2": ["crammed"], "-0.7 5.3 6.7": ["definitions"], "0.9 7.4 1.0": ["spontaneous"], "1.4 6.8 1.5": ["stewardship"], "2.8 6.6 16.6": ["parishioners"], "5.3 2.9 21.1": ["sperm"], "-1.2 15.0 8.9": ["bunt"], "12.5 6.6 2.1": ["saturated"], "9.5 11.0 5.4": ["stockpile", "debunker"], "-6.4 -2.1 14.0": ["condominiums"], "-1.7 5.2 1.0": ["paragraphs"], "15.0 35.6 2.8": ["warriors"], "17.4 5.5 6.8": ["attendant"], "10.3 13.8 24.0": ["bites"], "-4.6 3.7 1.4": ["reprinted"], "6.4 6.4 6.8": ["tones"], "2.8 2.2 5.4": ["tabs"], "3.0 9.7 13.0": ["stumps"], "9.2 -2.5 11.0": ["vinyl"], "-2.7 0.2 9.9": ["attire"], "-3.4 18.4 6.0": ["peacekeeping"], "-8.1 17.1 2.7": ["faiths"], "11.7 2.2 8.0": ["bells"], "8.6 22.2 2.7": ["wrath"], "3.2 20.7 13.1": ["hunted"], "9.8 2.8 22.1": ["chopped"], "7.2 -2.1 -3.8": ["fruition"], "10.6 7.0 16.2": ["microwave"], "7.1 2.3 4.3": ["con"], "3.6 8.8 5.7": ["optimum"], "2.8 6.6 -2.7": ["assuring"], "12.8 1.1 6.9": ["retro"], "19.0 9.9 3.9": ["portals"], "1.3 8.4 3.9": ["nurture"], "12.7 14.6 0.4": ["ironically"], "12.2 10.4 11.7": ["pops"], "-2.1 2.0 5.9": ["geothermal"], "-0.2 7.9 7.4": ["concedes"], "18.8 7.6 4.7": ["unsolicited"], "1.1 14.9 1.1": ["exchanging"], "8.3 12.2 4.7": ["draining"], "-10.1 4.2 7.5": ["withdrawals"], "0.3 13.0 3.7": ["braking"], "9.9 7.9 9.5": ["blizzard"], "12.6 4.3 0.3": ["hyped"], "15.0 3.8 9.0": ["cafes"], "10.6 9.6 4.0": ["snatch"], "2.0 9.7 -3.3": ["assertions"], "-2.5 13.5 -1.4": ["extradited"], "-4.5 0.7 8.1": ["violin"], "12.3 16.8 15.4": ["vampire"], "9.6 15.4 9.2": ["cinematic"], "3.6 3.1 14.7": ["docked"], "-4.6 1.3 3.0": ["delinquent"], "1.6 -3.5 -2.0": ["internship"], "9.8 17.1 13.9": ["spectator"], "8.7 9.2 5.1": ["dependency"], "11.0 2.6 1.5": ["unaudited"], "-0.2 10.8 3.4": ["entourage"], "-5.1 0.4 8.7": ["schizophrenia"], "7.8 0.5 23.3": ["squash"], "-7.0 18.2 5.8": ["disrespect"], "-2.3 3.8 6.6": ["indulge"], "1.4 5.6 2.5": ["intervals"], "8.6 8.0 0.8": ["typing"], "9.4 16.7 6.0": ["inferior"], "1.0 4.4 1.1": ["orphanage"], "15.2 -0.9 12.3": ["scrapping"], "0.6 7.0 8.6": ["overlap"], "-6.0 12.3 0.9": ["victimized"], "1.3 2.5 -4.5": ["relinquish"], "3.4 5.8 10.9": ["adolescent"], "-1.5 11.6 10.9": ["humane"], "25.6 6.6 7.7": ["tallest"], "2.6 10.9 6.1": ["bordering"], "-4.9 12.2 16.0": ["defensemen"], "5.8 3.3 12.5": ["genetics"], "0.1 7.1 6.2": ["understandably"], "13.3 6.9 0.6": ["hurled"], "11.4 -2.3 0.5": ["heralded"], "6.6 2.0 5.0": ["wiring"], "1.4 11.1 -2.0": ["interacting"], "4.2 0.8 11.3": ["testosterone"], "8.6 27.1 6.6": ["firepower"], "3.7 11.5 3.9": ["hallmark"], "12.7 11.9 5.8": ["blatant"], "3.7 9.9 0.6": ["extinguished"], "8.9 3.6 6.3": ["lowers"], "20.0 15.7 5.9": ["carmaker"], "4.7 9.7 4.2": ["loopholes"], "15.2 5.1 4.2": ["plethora"], "12.9 8.3 1.7": ["enthusiast", "rending"], "4.3 12.0 10.7": ["shopper"], "-0.6 12.3 9.5": ["biblical"], "17.4 40.7 5.5": ["invading"], "-7.6 5.9 1.2": ["vocalist"], "11.0 5.9 14.2": ["murky"], "-3.2 14.0 7.7": ["camaraderie"], "10.0 3.3 8.3": ["pensioners"], "16.3 9.0 20.6": ["tug"], "4.2 13.8 6.5": ["cues"], "11.6 9.8 2.5": ["chatter"], "1.6 20.8 6.5": ["impunity"], "5.4 6.6 6.9": ["unharmed"], "10.4 16.2 13.6": ["choke"], "1.0 15.8 3.8": ["incompetent"], "-3.3 -0.8 7.2": ["vocational"], "-3.8 11.7 -0.5": ["compromises"], "6.4 8.3 10.4": ["playful"], "9.8 -0.6 5.1": ["reckons"], "-0.5 8.8 3.4": ["familiarity"], "5.0 4.2 10.1": ["estimating"], "2.7 7.0 12.0": ["crafting"], "-3.1 28.2 5.6": ["betrayal"], "8.0 0.9 3.6": ["saddled"], "2.2 -3.0 1.8": ["matured"], "7.2 7.0 1.3": ["outpouring"], "1.9 16.5 0.0": ["harassing"], "8.7 -0.2 -5.0": ["refurbished"], "15.7 25.2 6.9": ["outpost"], "-1.7 22.9 0.1": ["collaborators"], "-3.9 8.5 -4.5": ["impartial"], "17.4 5.9 7.6": ["gears"], "12.1 2.0 1.6": ["wandered"], "-1.6 20.0 0.4": ["insults"], "7.0 15.0 18.4": ["natives"], "-4.4 2.7 -1.4": ["accrued"], "11.0 16.7 1.6": ["skeptics"], "13.4 2.0 10.4": ["snag"], "5.4 11.0 18.0": ["climbers"], "19.3 4.8 10.6": ["fountain"], "12.8 13.4 8.4": ["smells"], "6.7 14.2 4.8": ["rotate"], "6.9 17.6 18.3": ["ashore"], "13.2 21.7 4.6": ["mastermind"], "2.8 3.2 5.6": ["eclectic"], "3.4 2.2 16.3": ["cocoa"], "0.1 4.5 5.6": ["secretaries"], "1.5 15.6 6.8": ["ignores"], "-0.1 9.3 23.2": ["desserts"], "1.6 -5.7 7.7": ["cashed"], "1.9 27.6 3.1": ["assailants"], "11.9 2.1 12.2": ["firmer"], "12.8 1.4 9.3": ["goodies"], "20.5 1.5 -5.1": ["kiosks"], "9.4 3.0 3.7": ["scant"], "16.0 1.0 20.0": ["tin"], "11.1 -1.9 6.2": ["midway"], "12.7 25.0 5.9": ["dreaded"], "-4.0 11.6 6.4": ["funerals"], "-3.3 15.3 9.2": ["yardage"], "9.5 5.9 10.4": ["parades"], "9.3 10.7 11.3": ["telescope"], "5.3 7.3 13.4": ["onshore"], "0.9 13.5 5.5": ["scars"], "14.5 10.4 4.5": ["swipe"], "11.4 1.9 2.7": ["surrounds"], "5.5 13.3 8.0": ["playmaker"], "32.2 2.1 15.7": ["oversized"], "-3.6 4.9 4.1": ["regimen"], "11.2 9.7 11.3": ["defying"], "13.5 -1.5 4.8": ["shuttered"], "6.4 16.5 13.3": ["diminishing"], "-3.5 11.1 3.8": ["frank"], "11.5 7.3 7.6": ["paused"], "-2.4 19.9 4.5": ["cadets"], "4.0 8.0 7.7": ["don"], "4.2 12.6 0.9": ["tragedies"], "1.4 5.6 1.7": ["tweeted"], "3.0 4.4 -0.6": ["affirming"], "-1.2 16.8 5.2": ["sorrow"], "9.7 0.7 1.3": ["usher"], "6.6 15.2 5.7": ["inherently"], "-1.8 4.6 20.0": ["vegetarian"], "7.4 6.0 4.1": ["exert", "haematologists"], "13.5 -2.9 2.0": ["regulates"], "10.2 -0.2 5.6": ["pens"], "5.0 10.0 1.0": ["immensely"], "-6.8 1.6 7.4": ["dialysis"], "20.4 0.9 3.4": ["fiasco"], "12.6 4.0 9.4": ["la"], "9.4 26.8 9.2": ["maneuvers"], "9.3 3.1 -4.7": ["resigns"], "-0.4 19.3 8.6": ["hesitation"], "9.9 16.6 10.5": ["pointless"], "-2.6 12.6 4.9": ["assay"], "5.1 6.2 9.0": ["etiquette"], "16.9 10.6 3.5": ["arenas"], "-5.9 5.0 7.7": ["nominating"], "8.1 0.8 1.3": ["rebuffed"], "6.3 7.9 0.3": ["peripheral"], "12.1 2.8 11.8": ["carriage"], "5.3 17.9 8.9": ["utter"], "2.6 2.7 -1.1": ["behaved"], "3.0 7.7 0.7": ["rioting"], "-1.4 1.3 -0.6": ["ratify"], "6.6 8.6 0.2": ["cooperated"], "1.8 13.1 5.3": ["dispersed"], "4.8 4.8 -3.9": ["negligent"], "-1.4 9.1 1.0": ["influencing"], "2.9 11.9 4.8": ["erode"], "-6.7 5.7 5.7": ["scripted"], "0.8 7.3 9.2": ["needles"], "-1.2 17.5 7.0": ["viewpoint"], "8.9 5.7 9.5": ["smacked"], "1.8 11.6 5.5": ["casket"], "8.4 12.2 11.7": ["polluted"], "9.1 8.1 12.7": ["casts"], "4.6 10.4 3.4": ["openers"], "1.9 5.4 0.5": ["engages"], "9.2 8.7 4.6": ["brilliance"], "11.9 6.7 4.4": ["railways"], "6.8 10.9 5.4": ["resorted"], "14.0 7.2 9.2": ["penchant"], "-0.6 3.8 10.7": ["diabetic"], "9.8 -4.4 7.2": ["reprieve"], "15.6 5.0 10.7": ["cathedral"], "3.0 2.0 -4.5": ["entrusted"], "12.7 6.1 -2.6": ["defective"], "10.7 3.7 0.5": ["romp"], "11.7 8.2 8.5": ["wow"], "4.0 1.1 2.1": ["bulletin"], "8.1 4.6 16.9": ["boiling"], "1.7 21.3 9.7": ["yell"], "-2.8 3.8 2.7": ["dissatisfaction"], "-2.9 7.1 1.1": ["disagrees"], "16.6 -0.5 10.9": ["skyrocketing"], "4.6 18.2 4.2": ["dissident"], "16.0 8.4 2.0": ["assembling"], "6.5 1.4 5.6": ["lax"], "0.7 8.6 1.7": ["discouraging"], "1.3 5.4 0.9": ["poise"], "-0.9 -0.4 11.0": ["paychecks"], "9.7 5.4 4.6": ["envisions"], "16.5 1.6 6.0": ["toddlers"], "4.0 9.5 3.0": ["dependable"], "3.7 7.9 20.3": ["bloom"], "10.5 1.0 15.7": ["decorative"], "0.6 0.8 9.3": ["guitars"], "18.5 5.3 10.4": ["lagging"], "8.5 9.1 24.3": ["coasts"], "7.9 -2.9 4.8": ["pedigree"], "4.2 17.6 2.0": ["intensely"], "8.0 3.5 -5.1": ["diagnostics"], "16.0 24.1 10.5": ["superhero"], "9.5 6.4 -1.5": ["reminders"], "6.1 10.7 3.2": ["profoundly"], "-6.3 7.8 8.8": ["itinerary"], "3.7 21.5 10.2": ["kin"], "16.0 21.2 6.5": ["unstoppable"], "-2.3 15.3 3.1": ["limitation"], "-0.8 2.2 4.4": ["reuse"], "1.0 3.1 3.5": ["eluded"], "23.4 2.0 0.6": ["pretax"], "25.6 4.4 12.2": ["namesake"], "14.6 3.4 15.7": ["halves"], "2.9 15.6 1.0": ["bodyguards"], "0.3 6.4 15.2": ["bulbs"], "10.2 6.4 0.5": ["preacher"], "17.9 18.2 8.6": ["hack"], "12.2 18.3 8.9": ["socialism"], "-1.8 8.7 9.8": ["precincts", "fabs"], "11.7 4.0 11.9": ["racket"], "-1.5 10.7 10.7": ["descendants"], "5.8 3.2 3.3": ["videotaped"], "2.8 13.7 -0.1": ["mourn"], "28.2 7.4 6.5": ["swallowed"], "-1.2 2.3 -1.9": ["soliciting"], "5.1 3.6 1.5": ["administering"], "16.4 0.9 20.5": ["skeleton"], "1.0 1.6 0.1": ["ideally"], "18.0 8.4 12.9": ["dot"], "16.7 4.7 4.0": ["slams"], "14.7 43.8 6.7": ["armies"], "21.7 -2.6 -1.9": ["sues"], "-0.0 7.6 9.0": ["landslides"], "10.3 11.2 7.4": ["radioactive"], "13.4 12.4 7.0": ["worthless"], "6.7 25.1 2.3": ["sins"], "-2.6 -2.2 4.8": ["pharmacists"], "3.5 7.1 -2.3": ["configured"], "1.2 7.7 1.8": ["agitation"], "1.1 -1.3 3.6": ["premieres"], "-0.3 2.0 -3.9": ["receptive"], "1.5 7.3 16.8": ["whiskey"], "17.0 13.8 3.4": ["lowly"], "3.2 12.2 1.1": ["bullied"], "7.6 5.1 6.0": ["exodus"], "21.4 6.6 10.6": ["sturdy"], "0.3 8.4 2.0": ["residual"], "26.0 -0.2 15.6": ["cardboard"], "8.4 11.0 4.8": ["outlawed", "imbeciles"], "4.6 6.2 11.6": ["sticker"], "5.0 7.9 13.0": ["taxis"], "4.7 11.5 -2.3": ["responsibly"], "7.0 12.0 19.9": ["trapping"], "4.9 3.2 11.3": ["shave"], "-1.0 12.6 1.4": ["outplayed"], "8.4 9.9 11.2": ["candle"], "-0.2 8.7 8.5": ["boxers"], "12.6 2.7 3.7": ["experimenting"], "0.4 7.6 2.3": ["journeys"], "8.7 7.3 0.6": ["purchasers"], "-7.4 4.3 1.8": ["equalized"], "4.4 8.9 3.1": ["conspired"], "6.1 13.5 6.9": ["knack"], "4.6 0.1 -3.3": ["investigates"], "-0.0 8.2 5.0": ["invoked"], "6.9 -0.3 5.4": ["suitcase"], "5.8 2.0 1.6": ["certify"], "9.3 -0.3 2.0": ["nears"], "4.7 7.1 1.2": ["hugs"], "-10.4 0.6 6.4": ["homebuyers"], "6.3 0.2 -0.4": ["sourced"], "-0.1 6.8 22.0": ["soybean"], "12.7 8.7 4.0": ["grouping"], "4.2 13.5 12.6": ["sickness"], "14.6 3.8 6.1": ["riches"], "22.4 15.3 22.1": ["monkeys"], "1.8 4.5 2.6": ["persisted"], "-5.5 6.6 8.6": ["remorse"], "17.0 -4.5 9.8": ["expo"], "12.0 -0.2 3.0": ["signage"], "6.1 4.5 2.0": ["unheard"], "-3.5 9.1 4.7": ["sexually"], "12.1 2.2 6.3": ["bleachers"], "-5.0 6.2 4.3": ["interpretations"], "2.6 6.4 19.8": ["booze"], "7.6 10.4 11.0": ["disgust"], "8.9 9.6 14.3": ["downright"], "6.4 13.4 5.9": ["kissed"], "6.8 4.7 3.4": ["vitamins"], "7.5 22.8 7.3": ["treacherous"], "8.7 4.2 -1.4": ["flanked"], "5.8 9.1 19.4": ["surfers"], "7.2 -0.0 1.2": ["stardom"], "-2.1 13.9 3.9": ["irrespective"], "1.2 10.6 1.3": ["theoretical"], "9.5 18.0 6.6": ["myths"], "7.9 15.7 11.1": ["hose"], "20.9 3.8 -5.4": ["acquires"], "5.4 6.6 10.0": ["dismay"], "7.1 4.3 15.8": ["dips"], "8.1 4.1 18.1": ["goats"], "6.7 9.6 12.8": ["importers"], "0.3 5.6 16.3": ["tan"], "13.0 -5.2 9.8": ["tacked"], "6.2 11.7 5.0": ["foiled"], "10.6 15.2 7.8": ["stab"], "8.4 5.3 3.4": ["outweigh"], "8.2 1.0 2.3": ["outperformed"], "11.7 2.2 2.2": ["bandwagon"], "17.0 3.8 8.0": ["flashy"], "10.9 6.7 5.4": ["dashboard"], "2.5 -3.0 1.0": ["belted"], "-1.9 28.6 1.2": ["bravery"], "5.8 16.5 6.1": ["intrusion"], "11.8 -1.2 5.9": ["hiked"], "10.2 0.3 10.5": ["tenders"], "-5.7 4.0 3.7": ["rehearsals"], "-1.4 -3.0 4.6": ["tutoring"], "-0.8 28.1 4.0": ["immoral"], "-3.4 16.8 -7.4": ["sect"], "13.8 3.9 6.5": ["stoked"], "12.4 9.0 5.0": ["capitals"], "12.6 2.1 1.5": ["greener"], "-1.8 -0.2 6.1": ["introductory"], "2.3 9.3 14.8": ["forearm"], "5.8 8.0 -0.5": ["cellphones"], "7.5 6.8 -0.0": ["persuading"], "2.9 3.3 2.8": ["ultrasound"], "13.2 -8.1 2.5": ["flocked"], "8.1 8.3 5.8": ["undercut"], "6.4 18.2 7.0": ["prosper"], "17.0 27.7 6.5": ["armored"], "8.3 17.2 7.5": ["raining"], "9.9 10.2 2.0": ["entrances"], "14.8 11.6 17.7": ["blades"], "-5.6 14.0 3.7": ["respecting"], "5.9 6.3 19.9": ["livelihoods"], "8.5 11.6 17.2": ["starving"], "-2.1 12.1 8.9": ["punts"], "0.3 9.7 2.9": ["disconnected"], "3.8 6.8 3.8": ["initiating"], "3.0 6.3 2.7": ["begged"], "6.1 2.1 5.9": ["stamped"], "12.0 -4.1 10.2": ["yearlong"], "-4.4 11.7 18.8": ["redistricting"], "2.2 -1.3 12.3": ["allotment"], "-3.0 -0.0 -1.4": ["facilitates"], "20.7 16.2 0.6": ["heartland"], "6.7 4.9 -1.6": ["staked"], "13.6 5.1 11.3": ["oval"], "12.3 3.3 -0.0": ["shuts"], "9.8 5.2 4.5": ["wealthiest"], "19.2 11.7 7.0": ["creepy"], "0.1 6.9 15.5": ["vodka"], "14.2 0.1 3.6": ["swamped"], "14.9 5.2 7.6": ["proportions"], "2.7 6.4 6.0": ["vomiting"], "1.5 11.3 -0.3": ["libel"], "2.5 23.3 3.0": ["communism"], "6.8 0.0 6.2": ["eclipsed"], "5.1 7.7 10.0": ["apt"], "-2.0 1.4 -3.4": ["styling"], "2.5 2.9 5.4": ["onwards"], "5.5 5.6 3.7": ["preferring"], "7.8 10.8 10.3": ["trespassing"], "-2.1 8.0 3.8": ["prosecutions"], "-4.5 3.8 1.8": ["differs"], "-0.9 3.1 1.5": ["moderator"], "8.9 7.9 5.3": ["cylinders"], "-0.6 0.7 16.1": ["cruises"], "2.6 8.7 3.6": ["indefinite"], "9.3 15.0 12.7": ["slider"], "-2.7 17.3 4.1": ["dwell"], "3.3 -4.4 3.0": ["complements"], "9.4 9.9 5.9": ["barometer"], "10.5 16.2 15.6": ["shovel"], "-0.0 14.1 3.6": ["implication"], "5.8 25.0 14.8": ["companions"], "20.4 22.0 14.1": ["metaphor"], "9.0 6.1 6.7": ["clicks"], "4.7 16.7 11.2": ["slaughtered"], "-7.2 8.3 6.8": ["crossings", "denomination"], "12.2 5.2 0.1": ["commonplace"], "9.3 10.1 4.9": ["gusts"], "8.3 19.8 11.3": ["dusk"], "7.7 17.9 7.6": ["toxins"], "-5.6 2.7 23.4": ["embryos"], "5.0 5.9 1.3": ["exhaustive"], "-7.7 20.5 7.7": ["firefighting"], "1.6 7.0 3.7": ["refine"], "8.7 7.1 2.2": ["embraces"], "24.5 0.2 4.4": ["swirling"], "-4.9 11.5 4.4": ["marginalized"], "3.2 13.4 -3.0": ["unsecured"], "-2.3 21.8 4.3": ["regroup"], "0.6 1.0 10.6": ["ed"], "13.1 14.4 4.3": ["poisoned"], "11.5 10.5 21.1": ["jack"], "7.8 0.5 20.6": ["kilogram"], "0.3 8.7 11.6": ["leash"], "10.2 4.7 9.9": ["template"], "5.3 10.9 3.7": ["unforgettable"], "9.3 1.3 10.7": ["hectare"], "9.4 4.2 6.8": ["abrupt"], "-2.3 13.7 7.9": ["healed"], "10.9 2.6 2.3": ["programmers"], "13.8 14.8 6.9": ["wiping"], "12.4 18.6 11.3": ["protester"], "3.3 2.2 0.9": ["headway"], "8.2 2.4 2.7": ["tarnished"], "8.0 4.9 0.8": ["cramped"], "7.8 5.4 2.0": ["shines"], "4.0 7.0 0.6": ["emphatic"], "-0.4 3.6 37.8": ["onions"], "40.5 1.2 3.4": ["tycoon"], "4.6 8.3 21.5": ["gulf"], "8.6 -1.3 6.2": ["unaffected"], "0.0 5.9 5.5": ["mattress"], "-2.3 0.6 1.9": ["stipulated"], "3.1 -7.8 2.1": ["bilingual"], "1.2 17.1 5.4": ["debilitating"], "4.7 5.6 2.6": ["abolish"], "16.8 10.6 3.7": ["fascination"], "-3.6 5.2 14.6": ["winery"], "13.8 12.6 14.4": ["lousy"], "2.4 8.1 8.1": ["offside"], "7.5 8.9 5.9": ["solidly"], "8.0 8.0 6.8": ["screwed"], "-3.0 -4.0 9.6": ["childcare"], "-0.6 13.2 12.3": ["tomb"], "3.6 8.3 11.5": ["nephews"], "3.8 15.6 -3.0": ["asserting"], "0.4 0.7 11.7": ["calcium"], "1.1 19.4 1.5": ["believer"], "5.5 7.5 6.6": ["academia"], "9.1 17.2 4.8": ["comforting"], "8.0 12.4 10.6": ["beams"], "3.0 10.5 6.2": ["disconnect"], "5.4 7.8 13.4": ["snowstorm"], "5.9 15.3 1.9": ["passions"], "14.0 10.0 6.5": ["cowboy"], "10.1 32.4 4.2": ["captors"], "2.2 9.0 1.4": ["coherent"], "7.4 -2.4 -4.0": ["loaned"], "-3.0 9.8 6.0": ["novelist"], "-2.2 4.1 3.7": ["nurturing"], "10.1 11.9 4.6": ["cheerleaders"], "3.2 16.8 4.6": ["incompetence"], "10.2 4.7 2.2": ["soured"], "11.2 4.5 9.0": ["maid"], "-1.4 -5.8 4.3": ["presenters"], "1.2 7.5 12.8": ["macro"], "3.1 22.7 3.3": ["murderer"], "-0.1 19.8 6.9": ["uniformed"], "8.0 3.9 5.0": ["tripped"], "24.3 4.0 8.7": ["giveaway"], "3.4 -1.6 5.8": ["triples"], "4.7 9.8 12.8": ["grit"], "-0.5 7.3 6.4": ["eviction"], "2.9 9.4 0.5": ["echoing"], "4.4 14.2 2.7": ["confidently"], "9.3 4.1 13.4": ["decor"], "1.6 12.5 -0.7": ["roadblocks"], "12.2 23.0 6.3": ["sinister"], "9.6 -2.2 11.1": ["bins"], "-0.4 -1.8 -3.8": ["bt"], "3.1 4.5 5.8": ["saddle"], "2.1 -2.2 -0.7": ["scrutinized"], "6.4 2.1 11.4": ["mailbox"], "-2.3 0.7 5.3": ["debit"], "6.0 2.4 10.2": ["domains"], "0.2 17.3 1.8": ["complacent"], "1.1 22.0 -4.7": ["allegiance"], "0.1 11.0 4.2": ["professions"], "3.1 11.0 4.1": ["demolish"], "3.9 30.9 16.7": ["instinct"], "12.8 21.4 11.5": ["capitalist"], "2.8 10.6 8.8": ["firewall"], "11.4 3.3 7.0": ["deepened"], "7.8 9.0 18.2": ["rust"], "4.8 24.3 5.1": ["accomplice"], "10.7 21.2 8.1": ["violently"], "32.3 42.5 22.9": ["monsters"], "5.3 12.0 1.7": ["fooled"], "3.4 -0.3 2.7": ["enriched"], "1.4 11.0 14.0": ["watering"], "-1.1 1.7 3.9": ["shorten"], "2.7 2.5 6.8": ["peaking"], "0.4 9.9 0.9": ["missionary"], "-0.8 -3.8 6.6": ["assemblies"], "23.4 11.1 38.8": ["rabbit"], "7.6 -1.3 3.2": ["embarking"], "11.6 5.9 5.0": ["ventured"], "-1.2 8.7 9.2": ["segregation"], "-0.0 11.9 9.1": ["proficient"], "-0.8 15.7 3.8": ["humility"], "-3.5 15.5 -5.0": ["chaplain"], "8.1 23.8 14.2": ["invariably"], "4.7 19.1 2.7": ["underdogs"], "9.6 16.6 8.2": ["ploy"], "5.4 6.5 10.5": ["wonderfully"], "-14.0 5.1 8.4": ["incarceration"], "4.7 0.6 4.2": ["valves"], "-0.8 23.6 -2.2": ["avenge"], "13.1 10.2 19.7": ["hooks"], "1.8 3.4 -0.5": ["leverages"], "4.2 3.1 6.8": ["tuning"], "2.4 0.9 10.3": ["archdiocese"], "7.5 1.6 10.7": ["soak"], "-2.3 5.0 27.7": ["salads"], "-4.5 1.7 5.3": ["discus"], "-9.0 2.8 -0.3": ["carded"], "5.5 8.4 -3.9": ["compel"], "5.0 9.7 12.0": ["messed"], "10.3 8.8 14.6": ["paste"], "15.7 15.0 9.6": ["daddy"], "4.7 3.5 19.0": ["specialties"], "5.3 2.3 40.1": ["spinach"], "13.4 8.6 15.8": ["glue"], "16.1 10.6 12.4": ["statues"], "11.9 2.4 3.4": ["gripped"], "7.3 3.1 3.7": ["prematurely"], "8.7 14.6 18.0": ["fleets"], "15.6 13.5 20.4": ["nut"], "6.4 9.1 5.4": ["hello"], "12.3 3.5 25.5": ["gourmet"], "1.2 8.7 6.0": ["characterize"], "15.5 6.5 8.6": ["shrunk"], "-4.5 14.4 2.2": ["critique"], "0.2 3.0 1.6": ["markedly"], "12.7 4.6 3.3": ["strewn"], "2.9 9.4 0.6": ["libelous"], "1.8 5.5 -2.9": ["lapses"], "2.1 2.7 5.2": ["magistrates"], "14.3 15.5 1.8": ["bashing"], "7.6 5.3 8.2": ["walkers"], "-5.3 4.3 18.6": ["wineries"], "5.6 3.0 -1.4": ["expansions"], "7.6 5.1 0.2": ["sophistication"], "7.9 6.6 2.5": ["vent"], "-1.4 9.0 1.9": ["tuberculosis"], "1.3 1.9 3.4": ["desktops"], "9.7 2.8 36.4": ["sausage"], "-0.1 13.9 4.5": ["treaties"], "2.7 2.9 11.0": ["hypertension"], "6.1 12.4 6.2": ["amazingly"], "5.4 6.9 6.9": ["arteries"], "4.7 11.6 5.9": ["restrain"], "8.7 9.2 15.2": ["flipping"], "6.3 5.3 9.3": ["softened"], "0.3 13.7 2.8": ["punishable"], "10.9 31.0 18.7": ["warships"], "4.6 6.5 -2.6": ["philanthropic"], "11.1 3.8 60.4": ["tuna"], "8.3 5.6 7.3": ["eccentric"], "-1.8 4.9 5.8": ["bittersweet"], "13.0 9.5 0.8": ["ablaze"], "1.2 4.0 11.5": ["austerity"], "-2.0 0.6 5.6": ["delegations"], "3.7 4.5 4.9": ["unsettled"], "-6.0 11.2 -0.8": ["preach"], "6.9 8.4 14.0": ["gems"], "5.1 9.8 2.9": ["anthem"], "14.7 8.7 4.8": ["glaring"], "0.1 7.2 5.9": ["hindered"], "2.1 -5.2 -1.3": ["revoke"], "6.8 19.2 3.8": ["unilaterally"], "3.8 6.8 1.8": ["setter"], "9.8 13.7 31.7": ["dove"], "11.3 17.7 2.9": ["sensing"], "8.7 7.8 3.8": ["frontman"], "13.6 9.7 13.7": ["sinks"], "6.0 9.2 7.6": ["beg"], "4.0 18.7 2.9": ["unreliable"], "6.9 4.4 -1.2": ["liberalization"], "11.9 5.8 4.2": ["subpoenas"], "10.0 8.3 8.4": ["pedal"], "4.2 8.4 0.1": ["reinforcing"], "-8.0 -1.6 -2.5": ["arrears"], "7.0 4.0 -1.2": ["camped"], "-2.7 7.3 -0.4": ["directives"], "13.2 7.5 2.0": ["jolt"], "1.5 8.6 8.7": ["hustle"], "-1.3 5.3 2.8": ["amends", "icatibant"], "1.7 6.0 7.7": ["augment"], "17.1 25.2 -1.0": ["axis"], "6.0 17.2 11.5": ["bushes"], "-1.3 10.9 4.7": ["proclamation"], "8.9 -1.0 3.0": ["unearthed"], "-0.3 7.1 2.9": ["reunite"], "8.2 11.2 7.3": ["springs", "pnictides"], "1.5 13.3 5.6": ["predicament"], "4.4 9.0 7.9": ["reliably"], "24.2 1.6 5.1": ["leapt"], "7.4 9.0 4.3": ["horrified"], "9.4 11.0 14.9": ["relish"], "-6.7 5.9 6.6": ["drafts"], "3.8 8.3 11.6": ["admittedly"], "3.9 4.8 0.3": ["handover"], "10.1 34.1 6.1": ["tyranny"], "7.5 -4.0 3.1": ["balked"], "3.4 6.9 20.9": ["cocktails"], "6.6 7.4 6.9": ["complexities"], "15.2 4.0 5.6": ["draped"], "3.2 0.2 5.6": ["entertainers"], "10.3 0.1 2.5": ["ticketing"], "1.1 8.3 16.4": ["slalom"], "4.2 15.7 7.5": ["dearly"], "11.7 6.3 8.1": ["payoff"], "7.8 7.1 16.3": ["tiles"], "6.3 6.9 34.8": ["ham"], "5.7 4.9 3.8": ["ponder"], "18.8 11.6 2.1": ["disguised"], "15.4 21.1 9.4": ["angels"], "12.2 7.0 6.6": ["reckon"], "-4.0 17.6 3.3": ["gunshots"], "-2.6 6.2 8.6": ["appointees"], "7.8 23.4 7.9": ["futile"], "-3.1 9.8 2.0": ["recourse"], "4.1 10.0 6.8": ["veins"], "7.4 4.5 4.8": ["softening"], "-0.6 16.4 9.3": ["symptom"], "-4.2 14.0 25.3": ["boaters"], "7.0 13.6 8.5": ["handlers"], "-5.1 4.5 3.0": ["compile"], "5.9 14.6 5.6": ["agony"], "-2.4 7.7 1.0": ["achieves"], "-0.8 4.8 5.2": ["pharmacist"], "23.2 0.2 2.6": ["adorned"], "4.8 6.6 1.2": ["fluids"], "4.4 5.7 13.5": ["kitchens"], "3.4 13.5 7.3": ["antibodies"], "3.1 18.1 -2.4": ["ambushed"], "0.0 0.8 5.0": ["edgy"], "13.1 5.9 3.8": ["dynasty"], "9.2 14.9 0.9": ["looted"], "0.2 1.6 2.4": ["clerical"], "9.0 15.1 5.5": ["visually"], "-1.7 10.6 2.6": ["baton"], "14.4 10.5 24.4": ["goat"], "-1.8 14.2 7.9": ["empathy"], "17.6 4.8 7.8": ["collapses"], "8.8 2.6 -0.3": ["downloadable"], "7.8 1.0 3.3": ["noticing"], "1.0 9.6 4.9": ["stanza"], "7.5 9.9 18.8": ["feds"], "6.9 5.6 17.4": ["plantation"], "7.0 12.5 13.8": ["devise"], "14.2 32.4 5.4": ["conquer"], "8.7 17.8 10.3": ["limb"], "3.7 6.4 7.4": ["macroeconomic"], "7.8 15.4 3.9": ["leveling"], "13.5 12.4 9.8": ["anew"], "3.3 1.8 3.1": ["documenting"], "6.7 9.4 10.1": ["fireplace"], "16.8 3.7 11.0": ["mainstay"], "5.6 18.1 4.4": ["escapes"], "9.6 4.9 9.5": ["requisite"], "-1.8 3.0 4.5": ["recoveries"], "0.9 -0.5 10.8": ["uptick"], "9.3 0.7 1.4": ["injecting"], "-4.0 5.5 13.6": ["mare"], "13.3 14.6 0.3": ["bursts"], "5.4 25.1 22.8": ["submarines"], "-3.5 5.0 1.2": ["abolished"], "8.9 6.9 0.5": ["inroads"], "2.5 3.6 10.9": ["patronage"], "8.0 0.8 -5.5": ["restructured"], "2.9 8.7 7.6": ["adventurous", "superalloy"], "2.8 13.0 10.6": ["manners"], "-2.3 5.4 3.2": ["townships"], "-2.8 5.7 7.3": ["congregations"], "2.2 13.1 4.8": ["gracious"], "2.3 11.4 -0.9": ["deposed"], "3.0 0.1 4.9": ["gel"], "-2.7 6.0 3.1": ["suspense"], "2.8 7.7 7.0": ["lull"], "-2.8 8.2 9.3": ["choreography"], "7.2 5.8 5.8": ["dissolve"], "5.0 1.7 5.5": ["brackets"], "10.0 19.1 20.4": ["organisms"], "21.1 7.1 3.7": ["leaps"], "0.2 -0.1 9.4": ["factored"], "-6.4 13.0 1.2": ["intellectuals"], "19.3 17.4 11.8": ["supremacy"], "0.8 9.4 5.9": ["disarray"], "4.0 6.3 41.7": ["onion"], "4.0 -2.3 -1.3": ["veered"], "8.9 12.0 3.3": ["contemplate"], "23.4 12.3 12.5": ["leaping"], "-0.4 1.1 5.7": ["revitalization"], "8.6 12.6 6.2": ["fiance"], "-3.8 11.6 2.6": ["contradictory"], "12.3 15.3 14.3": ["corpse"], "17.6 -4.0 8.8": ["buoyant"], "15.3 8.2 6.4": ["presses"], "7.0 5.2 6.9": ["blending"], "0.4 4.6 7.9": ["adulthood"], "7.4 2.4 24.4": ["cherry"], "3.6 7.1 -3.5": ["usable"], "1.5 25.1 8.9": ["unjust"], "-4.7 0.1 6.5": ["benched"], "9.3 11.3 0.6": ["airliner"], "6.8 11.9 39.8": ["dolphins"], "3.1 -8.0 -5.3": ["placements"], "2.5 -2.9 -7.1": ["suitability"], "4.7 7.4 2.1": ["anonymously"], "3.0 1.3 3.5": ["lifecycle"], "-3.7 10.1 10.5": ["duet"], "12.7 15.2 4.4": ["evidently"], "-8.1 20.6 4.5": ["listener"], "15.8 14.4 7.5": ["specter"], "5.5 7.0 15.8": ["hoop"], "-0.2 7.8 1.0": ["accuser"], "14.6 11.3 7.7": ["creeping"], "15.4 1.5 5.3": ["stacks"], "4.4 9.1 8.6": ["calorie"], "12.7 -4.9 12.3": ["crowns"], "6.0 2.6 0.7": ["controversies"], "10.2 13.6 14.1": ["pillow"], "7.7 13.1 13.2": ["congressmen"], "1.3 9.9 0.4": ["thesis"], "9.8 1.0 26.9": ["feathers"], "13.7 9.8 12.0": ["peculiar"], "-2.3 7.5 8.6": ["confinement"], "-4.0 10.8 6.9": ["prognosis"], "6.3 9.3 5.6": ["hips"], "6.8 5.9 -2.7": ["torched"], "19.7 10.5 3.7": ["heir"], "-2.8 11.6 9.4": ["inequality"], "7.7 15.9 5.9": ["dared", "eyesight"], "-3.3 6.2 -1.4": ["informs"], "11.6 6.9 18.0": ["pulp"], "6.9 6.5 7.9": ["unlicensed"], "6.5 24.2 6.1": ["loyalists"], "20.4 13.1 42.7": ["pumpkin"], "2.4 -3.0 1.8": ["grooming"], "-3.2 8.4 5.6": ["alcoholic"], "7.6 -0.0 -2.2": ["ushered"], "6.5 11.8 8.1": ["fiancee"], "-8.5 5.3 0.5": ["profiled"], "14.2 7.1 6.7": ["wheeled"], "3.6 -1.2 -1.0": ["chatted"], "-0.2 3.6 15.3": ["winnings"], "-1.1 29.9 7.6": ["provocation"], "1.2 8.8 0.3": ["diligently"], "5.8 24.5 5.8": ["civilized"], "17.4 9.8 19.9": ["stuffing"], "12.0 10.3 1.4": ["fragmented"], "1.3 4.0 -4.6": ["unnoticed"], "1.8 3.8 2.0": ["librarian"], "1.6 7.0 9.4": ["handicapped"], "5.8 7.3 2.8": ["sprinter"], "6.5 9.3 3.5": ["cautiously"], "6.0 17.2 9.0": ["geopolitical"], "9.8 14.6 5.0": ["zoom"], "-1.2 10.6 10.8": ["inheritance"], "4.6 1.1 2.9": ["environmentally"], "2.5 11.6 19.7": ["biodiversity"], "16.8 12.3 9.8": ["hollow"], "13.3 5.3 23.5": ["slices"], "13.3 -8.0 1.7": ["mulling"], "1.5 -0.1 4.2": ["landfills"], "14.3 8.1 -1.2": ["purchaser"], "-1.8 -1.5 2.6": ["supervising"], "4.9 4.0 0.9": ["molesting"], "12.8 18.1 -0.4": ["crusade"], "-3.7 7.3 11.8": ["trousers"], "6.0 0.9 12.4": ["tad"], "12.1 5.5 1.1": ["sprung"], "9.6 7.3 19.5": ["anchors"], "11.5 10.1 4.6": ["gripping"], "0.6 16.1 8.4": ["inaction"], "3.7 7.9 2.0": ["duly"], "21.2 11.3 0.4": ["blazing"], "9.5 9.0 11.1": ["sofa"], "8.6 -4.7 2.0": ["flared"], "18.3 6.3 -1.9": ["enlarged"], "16.6 15.7 6.7": ["hacker"], "13.1 4.1 -3.1": ["occupies"], "-0.9 17.4 5.4": ["acquaintance"], "3.2 1.6 0.6": ["flied"], "1.6 18.6 -0.8": ["sic"], "7.8 5.3 6.8": ["limped"], "9.4 6.8 27.9": ["burgers"], "13.0 15.4 1.0": ["fiercely"], "8.4 21.6 8.0": ["evade"], "13.8 15.7 15.1": ["corpses"], "-4.2 11.3 19.0": ["cultivation"], "8.5 3.2 4.6": ["catalogs"], "9.5 7.2 1.2": ["affinity"], "-2.2 11.8 6.2": ["divides"], "14.0 1.0 5.7": ["deregulation"], "-1.5 16.9 2.7": ["suicidal"], "-12.8 6.2 7.7": ["abstinence"], "0.9 11.1 10.7": ["sixes"], "5.0 9.1 1.7": ["regaining"], "7.0 5.8 -2.1": ["swapped"], "6.9 14.4 9.3": ["vocabulary"], "7.4 11.6 -2.1": ["crossroads"], "-4.2 5.2 15.1": ["garment"], "2.2 10.3 3.5": ["redeemed"], "11.8 11.4 7.8": ["onlookers"], "15.4 5.8 11.4": ["disco"], "5.7 8.6 9.5": ["noses"], "19.8 0.0 6.8": ["inched"], "9.8 10.8 8.4": ["racketeering"], "4.7 4.6 -0.9": ["notifying"], "-2.0 -0.3 2.6": ["retroactive"], "-5.1 5.8 0.5": ["assures"], "13.2 8.6 11.4": ["shakes"], "1.9 16.6 7.2": ["quickness"], "8.5 6.5 2.8": ["rammed"], "2.2 3.1 16.3": ["sodium"], "11.0 4.8 1.9": ["precursor"], "-1.4 4.4 -2.5": ["gratifying"], "1.1 21.8 8.5": ["homosexuals"], "20.0 5.7 4.3": ["mimic"], "7.2 0.1 2.8": ["headlined"], "-1.6 3.9 4.6": ["staffs"], "12.6 2.9 2.8": ["crest"], "8.5 6.0 25.1": ["seaside"], "1.4 0.7 1.7": ["remuneration"], "-3.2 6.3 3.3": ["captaincy"], "-3.9 10.4 3.9": ["briefings"], "-2.9 11.2 5.8": ["lenses"], "11.4 13.8 18.1": ["colonies"], "-4.1 15.4 -4.3": ["untrue"], "19.3 25.4 12.3": ["ghosts"], "7.3 8.3 8.3": ["pencil"], "0.2 8.3 14.4": ["colder"], "-4.9 14.4 0.5": ["preventable"], "6.3 17.6 0.1": ["forgetting"], "14.9 6.4 13.8": ["unload"], "-1.6 6.9 4.6": ["congested"], "14.9 0.5 13.6": ["funky"], "6.0 7.5 10.6": ["shuffle"], "7.3 5.9 8.2": ["tractors"], "-1.2 7.5 7.0": ["equaled"], "20.0 -6.1 3.4": ["inked"], "18.8 13.9 26.6": ["kings"], "-3.1 2.8 0.4": ["formulated"], "9.2 5.1 11.4": ["dads"], "5.0 8.9 -0.6": ["apologizing"], "1.5 2.4 15.6": ["puppies"], "15.2 9.0 15.3": ["rusty"], "-1.3 16.1 8.3": ["unnecessarily"], "7.0 2.3 5.4": ["vitality"], "0.4 -1.5 7.5": ["eyebrows"], "4.4 9.0 14.0": ["chipping"], "8.5 0.2 13.7": ["loosen"], "9.7 12.7 2.9": ["wander"], "-3.3 6.8 -1.1": ["ascertain"], "3.8 1.4 3.8": ["comparatively"], "11.6 4.7 10.1": ["lush"], "-8.4 3.0 5.1": ["overcrowding"], "0.5 4.3 14.7": ["condom"], "1.6 12.5 1.7": ["confess"], "2.3 12.8 3.1": ["chant"], "8.6 7.0 -2.2": ["scares"], "5.8 4.5 8.7": ["fouling"], "10.6 27.7 12.2": ["wicked"], "0.6 9.5 5.1": ["hindsight"], "10.0 9.2 4.2": ["kindly"], "14.7 5.3 2.9": ["narrower"], "11.9 9.9 5.7": ["impromptu"], "-3.3 14.0 3.9": ["dispatchers"], "16.9 7.2 -8.7": ["purportedly"], "9.1 -0.9 7.3": ["banked"], "16.9 9.9 4.9": ["hammering"], "2.3 6.3 6.9": ["chores"], "-3.7 8.8 6.0": ["shortfalls"], "-1.1 -3.8 1.4": ["panelists"], "12.5 11.7 7.1": ["hugging"], "3.5 6.0 15.3": ["evenly"], "4.1 14.4 10.5": ["impatient"], "12.1 11.8 15.1": ["spinner"], "14.5 9.6 24.1": ["marble"], "6.0 9.7 0.6": ["optimizing"], "-9.3 8.5 12.8": ["handguns"], "4.1 9.6 9.0": ["enzyme"], "10.7 13.8 3.7": ["hijacking"], "8.2 4.3 10.5": ["stump", "dreamcoat"], "-3.4 -1.6 5.2": ["tenor"], "6.0 13.8 17.0": ["nighttime"], "-0.0 -5.2 2.6": ["participates"], "11.3 19.5 10.4": ["idol"], "13.8 8.0 6.6": ["ft"], "2.1 8.2 0.6": ["commits", "avionic"], "12.8 15.0 8.2": ["manipulating"], "1.6 22.0 4.7": ["yourselves"], "3.2 -1.3 3.7": ["vie"], "-3.6 7.0 7.1": ["hardworking"], "19.7 14.7 8.7": ["intensifying"], "-1.0 13.3 9.1": ["ballgame"], "-0.9 3.5 4.6": ["cons"], "10.3 16.2 4.4": ["roam"], "1.6 4.5 9.9": ["initiation"], "3.0 4.4 6.3": ["photographic"], "6.9 6.5 8.7": ["emptied"], "8.3 9.6 13.4": ["snowy"], "11.3 8.8 1.3": ["triumphant"], "15.2 11.3 11.5": ["altar"], "4.6 5.7 -1.8": ["trumpet"], "7.6 5.7 8.0": ["skewed"], "9.5 -6.5 5.7": ["axed"], "8.4 15.4 11.8": ["currents"], "-1.7 6.2 -0.8": ["headphones"], "4.0 22.9 6.0": ["reinforcements"], "-1.3 2.1 7.3": ["transgender"], "16.0 13.4 12.0": ["metallic"], "19.4 2.6 12.8": ["assorted"], "2.4 16.5 14.8": ["canine"], "5.9 -1.2 5.1": ["sequentially"], "10.6 7.2 4.0": ["preferably"], "-2.1 1.8 -4.4": ["receivables"], "9.7 8.6 14.8": ["exquisite"], "1.1 15.2 3.6": ["perished"], "0.7 -0.4 -6.5": ["tributes"], "-2.5 17.1 4.1": ["misunderstood"], "11.7 5.8 12.9": ["bourse"], "-2.0 13.6 -3.1": ["vigilance"], "19.3 4.0 22.7": ["carving"], "6.5 -0.7 -0.1": ["fore"], "13.8 4.7 0.0": ["faint"], "5.9 21.8 0.1": ["indispensable"], "15.1 20.5 6.1": ["battleground"], "0.7 17.3 1.6": ["enlist"], "-7.2 16.5 9.7": ["verse"], "4.8 3.4 22.3": ["bake"], "22.5 7.5 13.9": ["sagging"], "1.6 14.2 6.1": ["fortunately"], "14.6 1.4 17.5": ["racks"], "3.6 8.0 1.4": ["induce"], "6.0 16.4 7.0": ["awfully"], "2.8 7.1 6.9": ["brainer"], "12.5 7.6 9.9": ["decorate"], "-4.6 13.3 9.7": ["mined"], "11.7 -0.0 8.2": ["thinner"], "14.5 11.2 14.5": ["bolt"], "8.1 3.4 24.2": ["reel"], "-0.9 11.4 7.9": ["ozone"], "-5.6 3.6 6.0": ["discrepancy"], "19.8 27.3 11.1": ["ferocious"], "2.0 14.2 2.6": ["unconditional"], "-1.8 10.7 5.1": ["tolerant", "repressed"], "1.0 13.4 7.0": ["hikers", "centroid"], "-1.9 4.2 7.4": ["threads"], "5.0 1.6 16.3": ["feeder"], "-8.9 5.1 1.7": ["observance"], "5.2 20.0 0.6": ["deceive"], "7.4 4.8 10.3": ["dorm"], "-1.1 9.9 27.3": ["spices"], "-5.4 10.9 2.8": ["undermines"], "-1.2 7.7 5.0": ["quantitative"], "15.0 0.8 6.6": ["lamps"], "3.3 11.4 -0.1": ["imbalances"], "10.7 3.9 9.3": ["raucous"], "-5.2 20.3 2.8": ["alias"], "0.5 18.6 -0.3": ["bodyguard"], "15.4 6.1 1.9": ["riddled"], "4.9 4.0 10.6": ["ticks"], "14.0 8.8 8.2": ["autos"], "16.6 4.5 4.7": ["blonde"], "-5.3 12.4 2.8": ["constable"], "4.5 8.2 5.5": ["customization"], "0.9 17.6 5.8": ["authoritarian"], "8.7 11.9 10.2": ["fragments"], "15.7 9.7 11.8": ["busting"], "15.7 31.1 10.4": ["demons"], "9.5 -2.6 0.7": ["encompass"], "0.2 7.8 2.4": ["complainant", "waveform"], "-2.1 2.1 3.2": ["dissatisfied"], "-0.8 -0.0 -7.2": ["commend"], "-1.1 9.6 6.2": ["franchisees"], "1.2 10.1 1.6": ["infrastructures"], "0.8 1.5 2.6": ["sacking"], "8.2 10.5 10.0": ["atmospheric"], "6.1 13.7 5.2": ["postwar"], "0.9 2.0 12.5": ["hydro", "bloomington"], "9.8 11.1 7.9": ["reliant"], "4.1 0.9 -3.0": ["focussed"], "8.6 41.0 6.3": ["commandos"], "10.7 0.7 6.5": ["bolted"], "11.6 9.8 9.0": ["descend"], "4.4 6.4 6.8": ["disgusted"], "15.8 9.3 4.8": ["disgraced"], "3.6 8.4 1.3": ["restroom"], "10.4 -4.1 0.1": ["bundles"], "-11.0 -3.5 -0.2": ["hospitalization"], "6.7 11.6 9.4": ["throttle"], "5.9 20.3 3.1": ["detractors"], "-4.0 6.0 -0.6": ["rehabilitate"], "-2.2 2.7 7.1": ["garments"], "14.8 7.5 1.6": ["clocks"], "15.9 8.6 7.2": ["crater"], "3.5 4.8 8.3": ["plateau"], "6.1 15.5 9.8": ["allergy"], "10.0 4.5 2.5": ["unravel"], "9.4 6.0 9.0": ["picturesque"], "12.9 2.2 4.5": ["offsetting"], "8.4 6.4 11.2": ["ceilings"], "9.2 0.4 0.5": ["institutes"], "7.8 0.2 -2.3": ["reputable"], "8.8 5.1 5.1": ["neatly"], "6.9 15.6 3.9": ["variant"], "-6.0 -3.7 3.1": ["reinstatement"], "3.1 4.5 19.3": ["boiled"], "4.5 10.2 7.4": ["caddy"], "1.6 4.1 -0.7": ["somber"], "3.9 6.7 6.9": ["folder"], "15.3 -1.1 2.6": ["sham"], "-0.5 11.6 -1.1": ["admirable"], "5.9 7.3 6.1": ["complicate"], "-6.2 4.0 13.9": ["comedies"], "6.8 11.6 4.9": ["veil"], "4.1 13.7 5.0": ["implying"], "10.6 5.4 4.0": ["muscular"], "7.1 23.7 -0.3": ["hijackers"], "16.0 -0.2 8.5": ["hovered"], "14.2 4.8 31.2": ["fried"], "29.1 1.4 2.8": ["exec"], "4.3 -2.4 2.2": ["burner"], "1.3 6.9 12.7": ["ensued"], "-0.2 3.5 14.0": ["gram"], "7.5 0.6 8.9": ["sequential"], "4.0 21.8 8.6": ["violators"], "9.1 4.7 10.7": ["tack"], "-0.2 7.3 5.6": ["overcrowded"], "-0.9 8.8 4.8": ["charisma"], "7.9 11.2 6.6": ["addictive"], "-0.3 8.9 3.5": ["offend"], "11.7 14.6 12.6": ["plow"], "8.6 7.8 4.6": ["summons"], "6.5 9.5 8.1": ["intrigue"], "-4.6 10.2 3.9": ["occupational"], "14.9 12.4 4.5": ["massively"], "10.9 3.8 10.5": ["cyclical"], "-2.3 4.9 12.3": ["kidneys"], "9.8 10.7 5.6": ["slightest"], "1.2 9.0 -1.5": ["exposes"], "15.1 7.8 10.2": ["facade"], "5.3 14.4 -0.8": ["innovate"], "6.0 10.4 1.2": ["haunting"], "6.1 10.8 2.2": ["stretcher"], "4.2 13.3 9.0": ["linemen"], "3.7 3.1 5.2": ["hotter"], "3.1 1.9 3.2": ["footballers"], "5.7 2.8 13.3": ["autistic"], "17.6 12.1 14.7": ["perpetual"], "-4.0 6.7 5.1": ["recurrence"], "8.0 7.6 17.0": ["waitress"], "8.2 5.4 24.8": ["peanuts"], "-1.0 -0.7 3.3": ["rosters"], "9.5 -1.4 -7.3": ["scanners"], "1.2 22.3 5.4": ["pretext"], "7.2 15.4 5.0": ["indifferent"], "6.8 14.8 -3.5": ["conveniently"], "3.5 1.4 7.7": ["donned"], "12.5 4.5 4.0": ["crept"], "16.1 5.2 6.7": ["nanny"], "26.9 0.4 5.2": ["venerable"], "3.3 -2.2 -3.3": ["appoints"], "2.5 8.0 16.7": ["cured"], "6.3 20.4 -3.8": ["humiliated"], "9.7 8.9 7.7": ["wherein"], "1.5 9.5 4.5": ["coordinates"], "17.3 12.9 5.6": ["simulate"], "0.4 -4.0 4.2": ["walkout"], "2.7 0.6 12.3": ["lawns"], "3.0 12.2 0.1": ["forceful"], "6.5 7.1 13.7": ["refiners"], "18.3 10.2 9.4": ["squeezing"], "5.1 1.7 6.9": ["towels"], "4.6 2.4 8.1": ["bedding"], "7.0 12.0 17.3": ["iceberg"], "4.5 2.2 7.9": ["fingerprint"], "3.1 2.5 9.1": ["chairmen"], "12.8 4.7 4.4": ["peek"], "1.5 7.8 10.3": ["teller"], "-0.3 10.1 -3.1": ["defamatory"], "2.8 5.7 4.7": ["fruitful"], "12.5 2.6 8.6": ["cord"], "4.4 7.4 5.3": ["fairways"], "-2.8 -1.5 4.7": ["deadlocked"], "0.7 2.5 2.2": ["scuffle"], "0.6 -0.4 6.3": ["dentists"], "13.7 2.7 9.1": ["mirrored"], "5.5 13.5 1.1": ["discriminate"], "2.5 -4.7 2.3": ["organizes"], "2.1 6.8 18.3": ["rowing", "receivings"], "12.2 8.9 3.4": ["customizable"], "3.0 11.7 13.6": ["policyholders"], "0.6 4.2 4.8": ["tenths"], "1.0 10.1 3.5": ["timeless"], "12.5 10.1 0.7": ["swapping"], "10.8 4.4 12.8": ["brewery"], "4.8 1.6 6.6": ["biofuel"], "-3.7 2.3 -0.2": ["faxed"], "-6.9 -4.7 2.2": ["resignations"], "15.1 6.6 3.6": ["thrashing"], "13.0 22.9 4.3": ["relentlessly"], "5.5 11.5 8.4": ["thankfully"], "3.6 17.9 -2.5": ["willingly"], "12.2 -7.8 1.9": ["shelved"], "1.9 17.5 12.2": ["dictates"], "14.7 10.3 7.1": ["newfound"], "3.0 -0.5 6.5": ["puzzled"], "1.1 8.4 0.7": ["heroics"], "6.7 13.8 9.4": ["wanna"], "0.0 4.0 22.2": ["maize"], "-7.1 7.0 22.9": ["bushels"], "6.7 9.6 10.1": ["breakdowns"], "4.8 18.9 2.9": ["complacency"], "4.0 7.1 20.0": ["delta"], "6.0 14.1 25.8": ["habitats"], "14.7 12.3 4.1": ["depict"], "6.8 18.4 -3.2": ["forcefully"], "-2.3 6.3 12.5": ["renters"], "8.7 11.8 8.8": ["priceless"], "6.2 8.3 2.4": ["plausible"], "-2.5 4.2 1.7": ["evicted"], "5.8 4.3 6.5": ["hinges"], "11.7 2.7 9.4": ["semiconductors"], "13.4 7.3 10.6": ["unloaded"], "12.9 15.5 25.8": ["butterflies"], "9.7 7.5 13.0": ["eclipse"], "11.2 10.9 6.8": ["ludicrous"], "-2.3 9.1 6.0": ["iii"], "2.4 6.9 34.0": ["turkeys"], "4.5 -5.3 5.6": ["retrospective"], "10.3 -0.2 6.3": ["prompts"], "13.5 9.3 7.0": ["appease"], "3.4 1.1 3.3": ["installments"], "-6.0 7.3 16.7": ["commonwealth"], "10.7 18.3 3.8": ["outlaw"], "5.5 3.5 9.5": ["cabinets"], "7.7 12.2 4.1": ["hardened"], "0.6 11.4 1.9": ["workplaces"], "2.9 1.8 0.5": ["sketches"], "-6.7 16.9 2.4": ["detain"], "8.1 9.5 15.1": ["reproduce"], "-2.5 8.2 7.3": ["frequencies"], "2.1 2.4 5.5": ["hooker"], "-1.6 22.9 -4.5": ["discredit"], "-8.6 2.7 -0.6": ["omitted"], "9.2 11.6 -1.2": ["virtues"], "-2.7 8.3 3.8": ["characterization"], "7.4 11.8 8.5": ["careless"], "12.4 35.5 17.7": ["marines"], "8.0 4.0 -2.7": ["philanthropy"], "10.0 -2.5 13.0": ["handmade"], "12.3 11.9 28.3": ["mammals"], "16.9 6.6 4.8": ["clutching"], "6.4 9.1 8.8": ["unfolds"], "13.0 6.5 8.1": ["motors"], "2.2 13.0 -2.0": ["objectionable"], "2.4 2.8 -0.6": ["chairmanship"], "-0.6 5.1 2.5": ["divulge"], "-4.7 -3.5 3.7": ["enrolling"], "-7.3 37.2 5.1": ["platoon"], "4.7 6.4 3.8": ["solidify"], "3.6 7.2 -0.8": ["disclaims"], "4.0 9.9 12.8": ["rituals"], "12.6 11.6 21.7": ["bounty"], "5.6 1.9 11.8": ["plated"], "9.1 8.9 31.1": ["docks"], "5.4 10.6 4.7": ["capitalization"], "8.0 12.4 10.0": ["creep"], "6.8 13.0 4.2": ["anthrax"], "16.6 13.6 5.9": ["stared"], "13.7 18.2 6.8": ["burying"], "16.4 3.2 11.5": ["enclosure"], "-1.5 6.7 6.3": ["lockdown"], "7.2 20.2 10.1": ["impulse"], "9.3 0.2 5.9": ["goers"], "7.6 3.9 4.9": ["reclaimed"], "8.2 12.8 1.0": ["progressively"], "18.7 4.0 -6.6": ["powering"], "3.3 12.2 2.9": ["anomaly"], "4.1 9.0 -1.7": ["criticizes"], "2.5 12.1 2.7": ["nationalities"], "-6.1 4.4 9.9": ["annuity"], "3.3 8.5 14.8": ["pregame"], "14.0 4.3 12.8": ["staples"], "7.0 10.5 4.2": ["pathways"], "-0.1 10.6 3.7": ["negatives"], "2.6 6.5 7.9": ["revert"], "7.2 7.3 3.9": ["curves"], "14.0 4.9 9.0": ["thickness"], "13.6 -0.4 2.9": ["clogged"], "7.5 11.8 6.8": ["mysteries", "defcon"], "6.0 8.6 12.6": ["damp"], "-3.9 -4.4 7.5": ["concurrent"], "1.3 10.2 9.8": ["cholera"], "2.6 1.2 4.4": ["embezzlement"], "7.7 15.3 12.0": ["eroding"], "11.5 11.5 7.5": ["surveying"], "14.5 1.0 9.2": ["startups"], "7.8 2.3 -2.3": ["commercialize"], "6.0 -13.8 -3.8": ["caters"], "-7.2 -0.4 6.4": ["visitation"], "21.7 19.7 6.1": ["primitive"], "-4.1 9.6 3.2": ["passages"], "0.7 11.7 1.3": ["evangelical"], "-0.7 2.1 19.6": ["antiques"], "5.8 2.1 8.5": ["redundancy"], "1.6 7.3 0.9": ["parallels"], "11.5 3.4 10.6": ["usd"], "7.9 4.6 -0.1": ["repository"], "-2.3 6.3 -1.0": ["vacate"], "-2.5 8.3 11.0": ["detached"], "26.8 0.4 15.2": ["extravaganza"], "7.5 4.7 7.2": ["hillside"], "8.8 9.3 -4.8": ["intrusive"], "0.5 3.8 13.6": ["osteoporosis"], "5.3 1.7 6.2": ["takers"], "-7.5 4.6 5.5": ["concussions"], "2.9 6.9 1.6": ["rant"], "10.6 1.1 3.0": ["outsource"], "-4.7 8.5 11.5": ["filmmaking"], "13.9 12.2 4.8": ["stumble"], "9.8 19.7 5.6": ["agile"], "-4.2 4.3 12.0": ["bluegrass"], "3.5 8.8 29.0": ["rod"], "1.9 13.0 0.1": ["marshals"], "1.9 5.4 7.4": ["cabins", "caddies"], "-0.7 10.4 8.2": ["differing"], "11.3 -7.0 4.8": ["kickbacks"], "3.9 8.7 19.0": ["pesticide"], "8.4 -0.5 1.5": ["ramping"], "4.0 12.6 1.6": ["comprehend"], "-1.0 14.4 13.8": ["starvation"], "2.9 11.3 6.0": ["displacement"], "-3.2 10.2 -0.3": ["fractures"], "-6.6 6.0 13.6": ["appropriations"], "3.1 8.9 3.1": ["stamina"], "15.9 13.4 5.3": ["stalwart"], "1.3 7.2 13.2": ["scarf"], "6.3 12.9 1.3": ["compatriot"], "10.5 13.0 2.7": ["molecule"], "1.9 5.5 2.2": ["thirteen", "unexamined"], "-3.4 11.0 4.5": ["cultivate"], "5.2 6.3 5.2": ["facets", "beable"], "10.3 -2.9 17.7": ["soy"], "23.3 11.3 5.1": ["darling"], "8.5 7.4 8.4": ["recreate"], "-4.3 8.2 12.6": ["witty"], "-0.5 11.3 4.9": ["realignment"], "8.8 7.3 1.9": ["bolstering"], "5.6 16.8 5.3": ["playbook"], "10.0 4.2 11.2": ["punctuated"], "4.0 6.3 5.1": ["watered"], "11.0 9.9 27.5": ["aquatic"], "12.7 0.3 -3.3": ["swayed"], "7.6 8.3 10.1": ["genome"], "4.2 13.6 15.1": ["guild"], "7.3 17.1 8.2": ["enraged"], "9.4 5.7 5.5": ["disposable"], "26.8 4.6 5.1": ["nascent"], "4.0 6.4 2.2": ["conception"], "9.6 8.5 1.3": ["plugging"], "1.9 6.5 24.6": ["fluke"], "15.2 3.7 1.6": ["enticing"], "-6.6 12.3 7.9": ["cultivated"], "-4.3 4.7 5.6": ["maternal"], "-0.1 5.3 2.9": ["rpg"], "3.6 9.1 11.4": ["satire"], "3.3 -3.1 0.2": ["holistic"], "10.6 4.4 6.4": ["fraught"], "7.4 5.9 2.9": ["algorithms"], "16.8 14.2 2.4": ["twisting"], "2.4 1.9 11.5": ["sen"], "-3.1 6.2 3.1": ["downtime"], "1.0 12.1 0.9": ["energies"], "4.8 8.5 6.0": ["bothering"], "11.7 10.7 7.3": ["dormant"], "-0.6 2.0 8.9": ["substitutes"], "3.4 7.3 1.8": ["authoritative"], "3.7 10.9 -1.2": ["exposures"], "6.4 6.7 22.3": ["biologist"], "0.6 -1.0 3.2": ["purity"], "6.0 6.7 5.8": ["archbishop"], "7.7 11.3 5.7": ["mastered"], "-5.1 6.0 4.0": ["completions"], "3.7 10.7 8.4": ["warden"], "5.7 15.6 8.6": ["monuments"], "-4.6 9.1 4.4": ["formulate"], "3.0 8.3 11.2": ["golfing"], "21.7 4.8 12.9": ["bloated"], "-8.5 13.4 5.0": ["threes"], "10.1 0.5 3.7": ["frail"], "3.1 4.9 5.2": ["pounced"], "6.5 12.2 11.4": ["jokingly"], "-3.4 7.9 8.8": ["recounts"], "2.9 8.9 4.4": ["necessities"], "9.2 12.5 4.8": ["polluting"], "6.6 19.7 6.0": ["heroine"], "13.4 11.7 29.8": ["bee"], "12.3 7.5 10.2": ["enclave"], "2.2 17.0 4.5": ["truths"], "8.4 0.3 11.1": ["tweaked"], "3.8 3.4 3.1": ["farce"], "6.8 29.8 6.1": ["vengeance"], "-5.3 5.2 2.0": ["reasoned"], "-2.8 -8.2 13.5": ["purses"], "9.7 4.5 15.4": ["wholesalers"], "1.0 2.0 15.5": ["aboriginal"], "4.6 10.4 18.8": ["towing"], "1.6 17.9 10.7": ["distrust"], "-3.7 5.7 7.1": ["villa"], "0.6 2.5 -2.7": ["upholding"], "2.3 1.5 -2.5": ["reiterate"], "3.1 7.6 7.5": ["sightings"], "11.3 6.9 3.6": ["localized"], "2.5 3.2 5.7": ["sneakers"], "-4.0 5.6 9.7": ["deductible"], "4.9 8.1 0.8": ["covenants"], "7.4 9.7 16.2": ["sweets"], "6.6 13.4 5.5": ["imaginative"], "3.5 3.5 12.3": ["spacewalk"], "-4.5 0.1 6.7": ["musicals"], "2.7 13.2 4.6": ["persistence"], "-3.1 12.6 3.4": ["traumatized"], "-2.8 3.6 11.2": ["comedians"], "15.0 12.9 3.9": ["underperforming"], "-3.4 5.1 -4.8": ["aspire"], "-8.3 9.7 11.5": ["caregiver"], "-1.2 5.8 10.3": ["inbound"], "13.2 21.6 -2.5": ["horrors"], "-12.0 2.7 1.7": ["academically"], "8.0 9.3 2.1": ["pontiff"], "-1.0 7.0 5.3": ["relays"], "13.0 7.5 9.2": ["feisty"], "-0.9 14.1 36.6": ["elk"], "0.5 8.5 13.6": ["sweater"], "3.3 20.5 5.9": ["shouts"], "13.4 -1.1 11.9": ["halved"], "12.7 3.5 16.1": ["tray"], "5.3 8.7 -0.3": ["denounce"], "18.5 16.0 7.8": ["hapless"], "-2.3 1.3 -2.4": ["molested"], "6.5 13.5 13.9": ["ya"], "-0.2 0.3 -2.6": ["quieter"], "-5.9 14.2 16.0": ["martial"], "4.9 1.2 9.3": ["mildly"], "10.4 18.7 5.5": ["rooftops"], "10.0 12.1 5.5": ["rescues"], "13.1 8.0 2.8": ["spotting"], "17.2 19.8 7.8": ["analogy"], "21.7 7.6 9.0": ["bounces"], "-1.7 -1.6 -5.3": ["serviced"], "10.4 18.4 3.2": ["salvation"], "-3.0 2.6 9.0": ["sentimental"], "15.7 9.5 7.2": ["spins"], "-3.5 7.7 2.8": ["engagements"], "5.3 4.3 22.5": ["spicy"], "-1.0 8.5 5.0": ["fragrance"], "3.0 6.8 2.6": ["derive"], "0.5 -4.1 -1.1": ["newsletters"], "12.0 -2.5 5.1": ["tidy"], "2.7 7.1 -0.1": ["accommodating"], "18.8 27.2 28.1": ["insect"], "1.6 2.4 1.1": ["aftermarket"], "13.1 5.2 16.0": ["dived"], "4.5 11.9 10.8": ["canyon"], "8.2 4.0 -2.1": ["uninterrupted"], "14.7 13.8 8.1": ["illustration"], "-2.7 3.9 7.6": ["dissolution"], "2.8 -1.1 6.9": ["complemented"], "4.6 38.7 15.2": ["weaponry"], "6.4 19.5 7.8": ["powerless"], "12.7 5.4 8.6": ["mishap"], "6.4 5.8 1.4": ["sprinted"], "7.9 11.3 11.0": ["ref"], "18.5 17.2 8.6": ["sucks"], "4.0 -2.5 7.4": ["skirts"], "16.2 -1.6 3.9": ["renaissance"], "9.0 6.1 1.6": ["raged"], "5.5 1.8 7.5": ["troupe"], "9.2 13.5 6.2": ["continual"], "-3.4 6.2 11.7": ["vaccinations"], "8.3 14.9 23.5": ["tigers"], "12.1 0.1 6.3": ["revolving"], "5.7 5.9 6.6": ["entails"], "5.5 -1.2 -1.2": ["selects"], "9.3 -0.1 7.6": ["multicultural"], "0.4 7.7 -1.6": ["memos"], "12.5 9.4 3.2": ["kph"], "4.1 11.5 -0.5": ["proponent"], "12.6 7.1 14.0": ["lame"], "10.4 7.4 14.3": ["punters"], "16.7 18.6 4.1": ["lurking"], "24.5 0.1 7.4": ["resembled"], "5.1 8.2 9.8": ["imposes"], "6.1 8.3 18.1": ["tile"], "8.7 -6.7 6.1": ["sponsorships"], "0.6 7.8 14.4": ["plutonium"], "-1.0 5.7 -1.7": ["emailed"], "0.5 17.5 7.4": ["realistically"], "-6.8 9.2 2.4": ["adherence"], "9.1 3.1 7.1": ["abound"], "8.7 -0.7 4.2": ["stalling"], "20.1 5.0 8.9": ["flagging"], "2.3 4.7 1.5": ["overdose"], "6.8 14.1 8.1": ["rushes"], "5.2 28.4 4.5": ["trenches"], "12.8 12.6 5.4": ["insignificant"], "17.0 17.3 9.2": ["squares"], "6.8 8.4 4.5": ["triumphs"], "5.5 0.9 -2.3": ["breakthroughs"], "7.4 -0.7 8.8": ["pared"], "0.6 11.2 18.1": ["bartender"], "8.8 7.4 8.9": ["fodder"], "-6.5 10.1 8.1": ["marital"], "15.6 11.3 6.3": ["importer"], "4.0 0.4 -3.9": ["furnished"], "28.2 12.7 15.6": ["dinosaurs"], "1.2 2.8 8.0": ["rundown"], "9.5 8.3 2.8": ["misplaced"], "0.7 12.1 8.3": ["putter"], "8.1 3.8 12.1": ["revelers"], "7.9 -1.6 9.4": ["forgo"], "18.7 23.8 10.0": ["stare"], "2.2 7.5 18.8": ["gamblers"], "3.8 10.4 8.7": ["unforeseen"], "5.4 20.9 -0.9": ["democracies"], "-3.1 17.2 3.2": ["mobilization"], "9.2 13.8 0.9": ["passers"], "7.3 9.1 -0.0": ["absorption"], "4.6 5.0 11.3": ["tweak"], "15.1 14.0 6.9": ["angrily"], "5.4 14.8 8.4": ["blocker"], "14.7 -1.5 3.6": ["hopped"], "-0.9 -3.5 -5.2": ["recorder"], "9.1 11.3 0.9": ["ultimatum"], "2.3 3.1 -0.3": ["detour"], "4.5 6.1 0.3": ["filtered"], "-3.6 8.5 3.8": ["feminist"], "6.3 9.3 9.3": ["mend"], "9.2 7.7 6.0": ["nagging"], "7.7 7.5 1.3": ["enthusiastically"], "2.9 13.8 2.7": ["drains"], "0.3 11.9 1.3": ["tarmac"], "0.3 10.9 1.3": ["intervening"], "11.0 11.8 8.8": ["curtains"], "0.5 14.3 0.8": ["remembrance"], "11.5 8.3 -1.6": ["cheaply"], "6.1 9.6 11.6": ["rug"], "10.1 6.0 11.9": ["boxed"], "-0.6 4.1 0.0": ["renovating"], "4.8 5.5 3.9": ["quantify"], "10.3 3.1 2.2": ["whirlwind"], "3.8 22.8 8.8": ["irrational"], "6.1 17.9 4.9": ["decency"], "1.5 1.6 4.8": ["surpluses"], "21.5 24.3 5.9": ["menacing"], "10.2 15.3 5.4": ["stunts"], "3.9 2.9 7.0": ["bylaw"], "3.7 17.1 -1.1": ["baseless"], "9.7 10.5 3.5": ["ostensibly"], "-5.8 6.0 1.5": ["observes"], "3.2 6.0 9.2": ["prolong"], "0.2 -0.9 -3.0": ["podcasts"], "0.7 6.4 11.4": ["propane"], "10.6 4.3 7.6": ["thrived", "dauntingly"], "-3.9 13.1 3.3": ["achievable"], "0.2 13.2 0.4": ["auxiliary"], "16.0 12.9 5.4": ["evolutionary"], "1.0 3.1 0.0": ["envisaged"], "6.0 -1.1 3.4": ["restarted"], "22.5 6.2 8.0": ["nifty"], "-1.6 0.6 0.9": ["heartfelt"], "0.9 -2.1 6.8": ["booklet"], "6.2 7.2 3.6": ["inspecting"], "4.0 8.9 1.0": ["materially"], "1.0 21.6 9.2": ["unavoidable"], "-0.2 -0.1 -4.2": ["resonate"], "5.3 0.3 1.3": ["nostalgic"], "12.2 13.6 8.1": ["rooftop"], "-0.3 7.4 4.3": ["degradation"], "-5.1 4.3 -5.6": ["supervisory"], "-3.9 -1.7 4.9": ["pastoral"], "6.9 3.2 5.9": ["implanted"], "-6.0 7.9 -2.9": ["declarations"], "0.5 8.3 0.2": ["perseverance"], "-3.5 25.7 3.6": ["liar"], "-3.8 28.8 -2.8": ["treason"], "5.6 8.1 0.1": ["sixty"], "0.3 8.3 5.0": ["visibly"], "19.4 0.1 -5.6": ["prominently"], "10.0 3.2 11.1": ["ballroom"], "4.0 7.4 4.0": ["squared"], "0.9 5.6 8.1": ["nieces"], "22.3 9.0 2.1": ["foothold"], "3.4 6.4 34.3": ["chili"], "9.4 13.2 -0.9": ["unsettling"], "14.5 2.5 0.1": ["complexes"], "8.7 3.1 -2.1": ["digitally"], "-2.7 2.4 -1.0": ["erred"], "3.9 21.3 6.6": ["fists"], "-9.9 4.0 -6.5": ["empowers"], "5.7 12.4 7.8": ["obstructing"], "-2.9 14.1 2.3": ["suppressed"], "13.4 10.0 22.4": ["granite"], "-4.1 6.8 -1.9": ["lien"], "9.5 6.0 -1.1": ["shunned"], "9.9 5.6 6.1": ["rhythms"], "11.3 1.5 6.5": ["beginnings"], "8.2 12.7 2.4": ["concerted"], "15.6 9.3 5.6": ["mocked"], "-4.0 7.8 7.5": ["layups"], "19.9 5.6 12.4": ["plummeting"], "10.5 1.5 9.9": ["glut"], "7.7 5.6 21.7": ["salmonella"], "3.0 4.6 -0.2": ["uploaded"], "5.2 5.6 8.0": ["rarity"], "12.0 7.5 12.8": ["choppy"], "13.4 12.5 47.7": ["turtles"], "12.5 5.3 7.4": ["hobbled"], "9.1 3.4 8.8": ["implements"], "-2.8 21.1 7.5": ["trait"], "1.9 9.5 4.6": ["awoke"], "5.6 3.8 7.5": ["vitamin"], "5.5 4.3 0.3": ["broadening"], "-1.2 6.4 4.2": ["autograph"], "8.4 5.2 7.6": ["curled"], "10.9 8.4 7.5": ["distinctly"], "-4.6 9.2 5.2": ["sincerity"], "10.0 4.7 75.9": ["lobster"], "7.6 5.0 1.4": ["roundabout"], "-8.1 4.1 0.5": ["insightful"], "18.0 14.0 18.5": ["legged"], "-6.7 23.0 5.0": ["superiors"], "2.7 15.4 7.7": ["opportunistic"], "10.7 1.0 5.2": ["faltered"], "15.4 8.0 10.9": ["er"], "-0.2 9.9 20.8": ["grazing"], "-4.8 7.3 4.3": ["bookstores"], "8.8 15.6 11.3": ["dots"], "13.9 4.1 18.1": ["karaoke"], "4.4 23.6 5.2": ["formations"], "18.4 3.7 5.2": ["glitch"], "-7.3 -0.4 3.4": ["prescribing"], "11.0 9.4 5.7": ["prank"], "29.8 0.7 5.4": ["execs"], "7.4 5.2 17.2": ["hearted"], "13.8 8.4 4.5": ["gasp"], "1.0 9.3 0.7": ["neurological"], "10.1 16.4 16.2": ["sunrise"], "16.6 2.5 9.1": ["petrochemical"], "10.7 -2.1 5.3": ["heyday"], "-9.8 6.9 7.4": ["poets"], "1.2 8.4 -0.0": ["cohesive"], "3.8 9.3 0.5": ["encrypted"], "3.1 11.6 -0.1": ["solace"], "9.1 3.3 1.1": ["shareholding"], "-0.8 12.4 5.3": ["girlfriends"], "5.4 16.3 -5.5": ["humbling"], "-9.4 2.0 1.6": ["composers"], "4.7 6.3 11.2": ["loosely"], "-3.1 5.0 8.6": ["furlongs"], "12.8 16.9 5.4": ["singular"], "0.2 13.4 4.7": ["runways"], "0.9 5.2 1.0": ["outscoring"], "-1.2 18.0 15.8": ["bitterness"], "8.2 4.8 10.8": ["weaving"], "2.7 10.7 1.1": ["variants"], "-3.0 14.7 -2.1": ["hardline"], "4.8 11.6 6.8": ["artery"], "7.4 22.3 3.7": ["destroys"], "15.0 2.0 2.6": ["luring"], "7.2 16.3 0.4": ["cheerleader"], "5.4 9.2 1.2": ["pitfalls"], "-0.2 3.6 34.7": ["dredging"], "8.3 6.7 5.3": ["mundane"], "17.0 10.0 16.2": ["clown"], "8.9 6.7 8.2": ["churn"], "5.2 10.5 2.3": ["hallways"], "-0.7 1.1 -2.9": ["acclaim"], "0.4 -1.9 -1.8": ["exempted"], "2.2 14.8 23.9": ["frost"], "10.9 18.0 -0.0": ["superiority"], "3.0 6.6 11.8": ["netbook"], "-1.1 6.6 4.3": ["rezoning"], "-5.6 7.4 2.6": ["commuting"], "-4.8 10.5 10.1": ["mic"], "4.8 19.1 7.6": ["nationalism"], "0.8 10.8 -0.6": ["jogging"], "-2.0 17.7 6.1": ["sirens"], "2.5 9.8 5.6": ["punitive"], "11.3 10.8 20.6": ["chalk"], "-0.6 12.6 8.6": ["understatement"], "-0.2 11.9 3.9": ["complains"], "11.0 18.6 11.8": ["maneuvering"], "9.2 7.4 7.7": ["slum"], "11.4 9.5 11.2": ["seeming"], "-0.5 15.9 5.5": ["extremes"], "-5.4 15.7 6.0": ["paramedic"], "5.1 4.4 6.4": ["cheerful"], "16.6 9.6 11.1": ["spewing"], "-0.7 10.6 6.3": ["anguish"], "14.3 12.2 30.4": ["chop"], "9.5 3.0 2.0": ["smelled"], "4.9 16.2 0.3": ["blazes"], "12.7 18.2 1.9": ["blunder"], "11.8 0.5 6.5": ["flamboyant"], "8.3 14.2 5.4": ["hypothetical"], "6.8 -1.4 8.4": ["upswing"], "-0.2 11.8 -0.9": ["motorcade"], "7.6 3.9 3.7": ["devoid"], "-0.8 32.0 6.6": ["mortars"], "4.9 10.4 7.1": ["displeasure"], "-1.2 18.4 3.1": ["contagious"], "11.9 1.6 11.1": ["hooking"], "8.3 3.2 22.6": ["greenhouse"], "1.9 21.2 15.1": ["chopper"], "12.0 30.4 4.3": ["drone"], "10.7 13.4 12.2": ["thunder"], "6.2 9.2 4.0": ["sweating"], "13.9 19.6 6.2": ["nightmares"], "1.8 17.4 4.7": ["adrenaline"], "-4.6 2.4 7.0": ["cutoff"], "7.9 6.7 17.3": ["golds"], "2.5 3.2 1.4": ["levies"], "-1.3 15.8 3.9": ["exiled"], "14.1 9.7 28.9": ["rabbits"], "12.5 5.5 10.9": ["splendid"], "11.0 2.9 2.7": ["ruptured"], "5.0 6.1 7.1": ["abandonment"], "3.3 -0.2 8.7": ["provisioning"], "4.2 16.0 8.1": ["jab"], "6.2 3.4 3.2": ["originating"], "17.9 5.1 8.9": ["dim"], "-12.8 11.1 -7.3": ["interrogated"], "8.2 13.2 8.1": ["meddling"], "-4.9 8.1 9.3": ["methodologies"], "18.5 7.0 7.3": ["surges"], "2.5 5.0 3.0": ["badges"], "12.1 3.2 19.8": ["cages"], "-0.1 11.3 12.2": ["proficiency"], "1.5 7.4 10.5": ["grammar"], "5.1 4.3 1.9": ["licensees"], "0.8 15.8 4.3": ["realism"], "16.6 3.0 5.9": ["dpa"], "1.1 12.2 5.3": ["insecure"], "-0.5 1.2 0.4": ["reformed"], "1.1 27.3 8.6": ["sir"], "-8.9 10.5 10.5": ["seniority"], "0.8 12.3 11.8": ["skier"], "7.0 7.7 -0.3": ["miracles"], "12.6 15.1 1.2": ["paradigm"], "1.7 5.5 17.7": ["skates"], "-4.1 -3.4 0.7": ["inquire"], "7.5 15.4 11.7": ["politely"], "-0.2 11.8 1.0": ["regrettable"], "0.8 2.6 14.6": ["midseason"], "3.0 20.7 -1.6": ["clandestine"], "6.8 11.6 6.6": ["irregular"], "-5.7 1.3 0.7": ["discrepancies"], "1.2 7.1 7.2": ["agitated"], "23.0 26.4 25.3": ["predator"], "3.8 3.9 3.3": ["inconclusive"], "4.3 6.0 12.0": ["cloudy"], "-7.0 15.1 -0.6": ["grievance"], "-0.6 3.5 3.6": ["restraints"], "5.3 8.3 -0.2": ["campaigner"], "0.2 1.3 7.3": ["afternoons"], "8.3 22.4 16.5": ["fort"], "6.7 9.6 -1.3": ["hanged"], "12.8 3.1 18.6": ["reeled"], "3.1 -4.3 2.6": ["boycotted"], "8.4 13.8 8.0": ["stereotype"], "8.4 6.8 10.7": ["addicts"], "0.2 5.0 5.8": ["segregated"], "1.6 29.8 8.6": ["inflict"], "4.5 6.8 7.3": ["putted"], "1.2 7.6 5.9": ["aspirin"], "3.1 3.4 -2.0": ["unattended"], "9.7 3.1 18.6": ["fossil"], "21.2 36.1 12.3": ["imaginary"], "5.3 6.2 1.2": ["intending"], "2.3 2.1 7.5": ["salvaged"], "10.0 2.8 10.4": ["generously"], "-2.8 2.5 8.6": ["substituted"], "4.0 9.6 9.7": ["paralysis"], "0.9 17.7 0.3": ["detriment"], "9.5 7.6 10.9": ["parody"], "9.1 -3.3 6.8": ["instrumentation"], "7.0 10.3 8.2": ["cling"], "4.2 1.1 8.2": ["commencing"], "31.2 4.4 7.4": ["resembling"], "-0.4 9.2 9.8": ["streaks"], "-2.1 6.8 1.4": ["relayed"], "16.0 18.9 7.6": ["unsuspecting"], "-3.4 14.6 5.4": ["theology"], "6.5 6.6 9.7": ["angst"], "11.0 10.6 5.6": ["pitting"], "0.9 8.6 3.2": ["refresh"], "14.2 1.0 13.0": ["pennies"], "17.9 2.9 33.9": ["aquarium"], "2.1 10.2 10.8": ["seeding"], "4.0 10.6 5.6": ["sheltered"], "6.7 2.9 1.5": ["crores"], "5.0 10.4 5.4": ["tedious"], "8.3 -1.0 -0.5": ["homepage"], "8.6 12.7 6.4": ["undo"], "4.5 4.9 20.1": ["migrant"], "3.3 8.3 10.0": ["furnace"], "10.7 7.4 14.5": ["accents"], "5.4 2.2 -1.0": ["flyers"], "-2.1 8.4 0.2": ["omissions"], "4.2 -1.1 7.9": ["baffled"], "-1.1 -0.2 3.9": ["freelance"], "4.9 5.2 2.7": ["custodian"], "2.1 3.7 7.0": ["noticeably"], "5.8 2.2 3.7": ["polish"], "1.7 17.8 4.6": ["melee"], "12.3 2.2 19.3": ["wax"], "19.0 2.7 2.2": ["kiosk"], "-0.3 7.6 2.2": ["unfit"], "0.7 7.1 1.8": ["elated"], "7.9 6.9 1.5": ["conceptual"], "8.7 1.2 4.2": ["cemented"], "6.4 21.1 2.4": ["trusting"], "5.0 3.8 14.9": ["stud"], "13.8 12.3 9.1": ["navigating"], "13.3 -2.0 5.0": ["infused"], "8.3 0.3 -0.0": ["exclusivity"], "14.1 16.0 -1.1": ["besieged"], "5.4 17.7 7.7": ["bystanders"], "14.9 14.7 0.1": ["stationary"], "5.7 5.1 20.9": ["eatery"], "15.2 11.7 25.3": ["lemon"], "9.8 -3.4 4.3": ["brochures"], "20.7 19.7 31.7": ["perch"], "-1.1 4.1 13.0": ["pickups"], "-2.2 7.2 2.5": ["rabbi"], "9.2 2.0 -4.7": ["representations"], "2.9 14.0 8.2": ["societal"], "10.0 -3.3 8.1": ["posh"], "0.8 -0.3 9.4": ["curtailed"], "11.9 -0.5 2.3": ["infancy"], "6.0 20.8 10.4": ["elites"], "6.1 15.7 14.5": ["famine"], "-1.1 13.9 7.8": ["melody"], "-5.5 13.4 20.5": ["opium"], "2.2 5.6 1.7": ["leakage"], "3.4 0.5 24.7": ["salsa"], "3.1 9.6 26.2": ["diner"], "7.5 -8.3 1.1": ["onsite"], "13.5 6.7 16.3": ["wacky"], "19.4 2.2 8.2": ["leaped"], "15.1 13.5 7.5": ["carmakers"], "6.7 5.2 3.9": ["capitalizing"], "2.2 11.5 -2.9": ["silenced"], "5.4 9.5 18.2": ["smoker"], "-1.7 12.5 -3.7": ["proactively"], "1.2 8.8 4.4": ["guardians"], "8.0 9.0 2.1": ["cinemas"], "-0.9 13.2 0.1": ["bothers"], "3.0 8.8 -0.5": ["usefulness"], "13.2 15.3 8.0": ["errant"], "6.0 10.4 2.9": ["mantle"], "-4.3 14.5 11.2": ["reelection"], "9.2 12.6 10.1": ["wasteful"], "2.7 -0.9 13.1": ["boiler"], "-4.7 2.1 7.4": ["repeats"], "6.1 8.9 3.4": ["defuse"], "-5.2 12.5 12.8": ["malnutrition"], "17.0 10.5 2.9": ["whipping"], "7.3 -1.3 3.0": ["coding"], "9.8 7.5 5.4": ["cumbersome"], "-2.8 1.4 3.9": ["remediation"], "10.6 10.0 10.1": ["zip"], "22.3 7.4 20.5": ["claw"], "-5.0 2.9 58.1": ["fishery"], "-2.6 6.8 -0.8": ["affirm"], "15.8 21.1 2.8": ["galaxy"], "-10.2 0.9 6.7": ["delinquency"], "19.6 7.3 18.8": ["rigging"], "2.9 0.3 14.3": ["necklace"], "-4.4 9.6 1.7": ["categorized"], "-7.3 2.7 -3.3": ["conferred"], "5.8 2.9 8.8": ["hinge"], "5.8 1.0 2.8": ["gathers"], "13.9 9.1 14.8": ["extinct"], "-0.5 17.1 1.8": ["repetitive"], "2.4 7.7 5.2": ["firings"], "-3.6 6.4 -3.0": ["rapes"], "3.5 6.5 5.4": ["aftershocks"], "4.1 2.2 7.1": ["dormitory"], "5.6 14.2 8.9": ["impede"], "17.1 8.1 11.2": ["slapping"], "8.0 5.1 5.1": ["microscope"], "2.5 21.5 4.3": ["fugitives"], "5.7 9.5 3.5": ["clutter"], "17.7 1.4 -3.1": ["touts"], "-2.3 5.1 3.7": ["spirituality"], "7.5 1.3 3.7": ["keyboards"], "-4.4 9.1 4.2": ["nodded"], "6.4 6.3 -1.4": ["alerting"], "-1.5 4.6 1.7": ["fluent"], "3.1 -3.7 2.2": ["refurbishment"], "12.1 6.8 9.7": ["braced"], "6.9 15.0 -0.8": ["failings"], "-3.3 5.5 11.1": ["comedic"], "-0.0 8.1 0.2": ["petitioner"], "17.5 1.9 17.7": ["flavored"], "4.2 14.2 1.8": ["staunch"], "25.2 12.1 11.9": ["maze"], "14.6 7.7 9.6": ["hopping"], "14.4 6.7 9.6": ["sheds"], "3.0 8.6 14.3": ["wheeler"], "12.1 18.2 3.4": ["rescuing"], "5.7 5.7 -1.2": ["translating"], "13.8 2.4 12.0": ["rockers"], "-0.3 9.1 14.6": ["goaltending"], "5.9 0.6 -0.9": ["undertook"], "14.9 9.3 1.5": ["noises"], "38.3 2.6 1.9": ["mogul"], "3.1 8.6 10.3": ["overpass"], "10.5 -1.4 4.3": ["clamp"], "3.3 11.7 -0.6": ["annex"], "-1.3 8.0 13.5": ["pasture"], "18.3 8.8 28.9": ["bamboo"], "7.9 8.7 11.1": ["devotees"], "-0.2 -1.4 0.1": ["voicing"], "16.5 39.5 7.9": ["nemesis"], "6.2 14.9 7.4": ["universally"], "15.5 12.0 8.9": ["bending"], "7.0 1.0 12.0": ["ribbons"], "6.5 7.5 9.1": ["nausea", "repegged"], "2.2 15.3 -4.2": ["condemns"], "10.4 -4.0 -0.1": ["beefed"], "1.3 -1.5 2.6": ["clauses"], "0.4 5.6 5.7": ["transitions"], "20.4 18.1 0.2": ["savior"], "-3.8 -0.0 -1.0": ["slotted"], "8.2 5.5 26.0": ["biologists"], "16.0 4.7 8.1": ["heap"], "12.7 6.5 9.2": ["staggered"], "-2.8 4.7 4.8": ["tallies"], "17.8 -0.3 3.8": ["flap"], "16.3 2.6 14.0": ["sizzling"], "14.0 10.8 5.7": ["trivia"], "9.1 8.1 4.7": ["ascent"], "-0.5 9.7 8.5": ["disapproval"], "12.0 10.7 19.8": ["monarch"], "4.3 1.6 5.6": ["revising"], "6.5 9.4 -2.1": ["moniker"], "-4.1 17.2 7.2": ["correspondents"], "5.6 4.1 3.4": ["burdened"], "-9.2 5.7 7.0": ["immunization"], "-0.1 29.3 -1.8": ["airstrike"], "17.5 14.0 10.7": ["ol"], "4.4 8.5 10.5": ["bickering"], "10.3 1.3 8.0": ["tussle"], "-0.2 14.8 5.4": ["estranged"], "15.6 8.6 6.4": ["stung"], "10.3 18.5 10.1": ["psyche"], "0.6 7.8 -2.6": ["uplifting"], "-3.0 10.7 7.5": ["amateurs"], "-2.8 5.7 7.9": ["learners"], "24.7 22.4 17.3": ["zombie"], "-7.1 4.0 2.8": ["upbringing"], "4.7 6.8 5.7": ["nap"], "11.4 2.3 11.9": ["gum"], "9.3 12.2 2.1": ["guise"], "-2.4 8.9 15.7": ["rabies"], "3.3 21.2 9.6": ["senseless"], "5.6 9.6 2.7": ["exhaustion"], "-3.7 2.7 -2.1": ["amending"], "4.9 1.2 6.8": ["h"], "12.0 17.9 5.9": ["solitary"], "8.1 15.2 7.1": ["simplest"], "-3.4 -1.0 -2.3": ["psychologists"], "1.4 29.0 0.4": ["radicals"], "8.2 17.6 8.0": ["mistress"], "12.3 0.6 6.0": ["plucked"], "-0.7 9.5 3.7": ["exhausting"], "9.2 59.4 7.9": ["adversaries"], "7.6 3.4 9.2": ["ha"], "11.8 9.7 100.0": ["crab"], "5.9 13.3 4.3": ["erroneous"], "9.3 27.7 2.9": ["waging"], "-6.3 11.5 5.2": ["psychologically"], "8.5 -0.2 4.7": ["buyouts"], "15.6 5.9 11.2": ["eagerly"], "7.2 21.5 10.9": ["indifference"], "8.4 16.5 4.6": ["adept"], "9.0 8.7 12.4": ["artificially"], "-5.3 9.1 6.8": ["regionals"], "20.7 6.0 3.9": ["boardroom"], "14.3 7.3 11.6": ["shrug"], "13.7 -0.3 8.9": ["carts"], "12.2 5.5 10.0": ["gushing"], "-0.5 17.4 1.4": ["intolerance"], "16.7 13.6 6.6": ["circled"], "-5.5 8.9 19.0": ["gardeners"], "-6.1 18.8 0.6": ["cherish"], "12.3 4.5 14.5": ["slowest"], "6.0 11.1 3.7": ["envoys"], "5.5 2.7 7.3": ["essentials"], "10.9 26.8 17.5": ["arrow"], "10.3 11.3 8.1": ["advertiser"], "4.2 17.8 9.7": ["tendencies"], "8.5 12.7 -5.9": ["bombarded"], "1.2 -1.1 8.7": ["connector"], "3.0 18.6 0.8": ["embarrass"], "1.1 6.3 3.1": ["soreness"], "-5.1 13.9 5.7": ["centrist"], "16.7 9.1 16.9": ["fuzzy"], "14.2 16.0 19.1": ["arcade"], "19.3 2.0 24.5": ["cranes"], "2.1 4.3 3.7": ["fibers"], "7.7 5.1 10.2": ["stymied"], "0.4 5.8 -0.2": ["completeness"], "-4.8 8.7 3.0": ["parliamentarians"], "9.1 7.5 16.5": ["bolts"], "10.3 5.0 2.9": ["racking"], "3.8 1.1 4.9": ["cameo"], "12.3 4.7 2.1": ["hastily"], "4.9 6.1 0.8": ["entail"], "2.1 14.3 9.2": ["chuckle"], "3.3 15.2 2.2": ["patrolled"], "8.2 12.3 2.5": ["trivial"], "9.5 5.0 -2.2": ["vandalized"], "11.5 10.4 6.1": ["stifle"], "8.8 3.3 -3.7": ["scathing"], "-2.3 4.6 -1.7": ["acquittal"], "10.1 12.2 0.6": ["reckoned"], "-4.0 14.9 3.1": ["uttered"], "21.2 19.2 10.5": ["crawling"], "1.2 13.6 6.2": ["constituent"], "21.4 10.3 7.5": ["stumbling"], "8.7 -1.7 13.0": ["quad"], "18.4 6.2 14.0": ["trough"], "-1.2 -2.6 -1.2": ["memberships"], "5.0 2.7 3.8": ["overflow"], "12.9 16.7 4.9": ["puzzles"], "19.7 17.2 18.8": ["lions"], "4.0 8.1 -5.2": ["disturbances"], "13.4 -2.2 1.0": ["stampede"], "4.3 10.6 -0.4": ["missionaries"], "-0.7 9.8 0.0": ["intoxication"], "3.5 20.2 -0.5": ["perpetrated"], "4.1 6.3 27.6": ["canoe"], "6.7 13.8 4.3": ["theoretically"], "6.3 9.1 4.9": ["unchecked"], "3.7 1.5 -2.1": ["verdicts"], "5.6 1.0 -1.9": ["alumnus"], "1.6 7.4 3.7": ["frivolous"], "-1.0 7.4 3.2": ["fourteen"], "5.1 8.8 2.1": ["averted"], "0.9 0.5 4.3": ["dismayed"], "12.0 0.9 11.2": ["cm"], "7.9 9.4 2.8": ["browsers"], "-2.1 7.8 -6.0": ["unbiased"], "6.3 14.2 4.4": ["egregious"], "5.6 1.8 30.7": ["sediment"], "23.1 0.0 3.2": ["spinoff"], "10.4 7.2 42.3": ["mushrooms"], "3.7 9.1 11.8": ["scarcity", "cyanidin"], "-4.2 8.7 11.7": ["appropriation"], "-5.2 10.4 10.2": ["backcourt"], "12.9 11.1 2.6": ["brazen"], "10.5 5.6 4.7": ["hyper"], "15.7 4.1 10.7": ["tepid"], "20.6 3.2 4.4": ["giveaways"], "-2.7 3.8 0.8": ["chats"], "-7.4 14.5 0.6": ["disrespectful"], "5.1 9.6 0.3": ["wept"], "-5.5 3.1 0.7": ["unsigned"], "6.6 11.4 5.4": ["aura"], "6.4 -4.2 0.9": ["diapers"], "9.3 0.6 16.3": ["ceramic"], "-6.0 3.5 5.3": ["bonded"], "14.1 3.3 7.6": ["emirate"], "3.7 3.0 1.7": ["diverting"], "14.0 3.8 3.3": ["consumes"], "9.6 14.4 8.7": ["visuals"], "8.2 -3.6 -0.4": ["discontinue"], "6.2 9.3 5.9": ["reseller"], "2.4 8.8 1.5": ["garages"], "4.9 8.9 3.0": ["inherit"], "15.8 2.4 27.8": ["bananas"], "14.1 8.1 22.1": ["chilled"], "14.2 2.0 1.3": ["bumpy"], "10.5 7.8 -2.7": ["restated"], "-0.8 3.0 6.7": ["subdivisions"], "23.7 6.2 2.4": ["folding"], "14.6 5.5 8.4": ["beset"], "6.8 -0.1 11.5": ["juggling"], "7.2 15.2 -2.9": ["blackmail"], "1.9 8.7 -0.6": ["blanked"], "6.2 13.7 10.3": ["torso"], "12.6 12.7 6.8": ["vandals"], "10.7 6.8 28.0": ["oak"], "14.3 12.0 1.5": ["storming"], "3.8 8.9 -1.8": ["harrowing"], "2.5 11.9 7.9": ["hypothesis"], "1.7 1.0 13.7": ["peso"], "12.5 0.9 15.0": ["wares"], "8.7 4.5 20.3": ["leftover"], "-1.2 -3.6 15.9": ["sampled"], "1.4 0.7 6.6": ["recap"], "7.8 17.6 13.0": ["hopeless", "safecracker"], "8.9 16.6 6.7": ["blindness"], "-0.2 6.1 14.7": ["fertilizers"], "0.9 6.7 14.6": ["gridlock"], "-5.7 8.8 -1.5": ["omission"], "16.0 15.7 3.0": ["unwelcome"], "15.5 18.2 3.9": ["overrun"], "13.4 7.3 -3.4": ["unrivaled"], "11.3 8.4 19.5": ["peg"], "1.1 7.8 8.1": ["formulas"], "7.3 17.9 -3.1": ["plotted"], "3.8 6.8 5.3": ["crutches"], "-1.7 14.2 10.7": ["caste"], "19.2 11.9 16.0": ["swamp"], "5.9 12.9 -3.2": ["leaflets"], "0.7 6.4 5.1": ["repealed"], "7.5 10.6 20.0": ["ecosystems"], "6.8 5.5 5.2": ["redirected"], "-1.3 9.7 1.6": ["commemoration"], "5.3 23.6 11.7": ["expletive"], "7.1 14.7 8.5": ["resorting"], "9.3 -7.3 -1.5": ["brainchild"], "8.1 5.9 13.5": ["replays"], "5.1 1.3 17.1": ["ornaments"], "1.4 -0.2 -0.5": ["competency", "nebuliser"], "-3.8 -2.3 6.4": ["coordinators"], "3.0 5.7 2.2": ["bogeyed"], "2.9 12.4 0.3": ["deterred"], "5.9 19.5 5.6": ["cameraman"], "7.4 3.0 6.9": ["penultimate"], "-1.2 25.6 5.0": ["retribution"], "9.8 9.2 20.7": ["dice"], "-6.0 5.7 6.6": ["disparities"], "15.3 3.9 7.6": ["fashioned", "embosses"], "6.3 5.1 28.4": ["supper"], "-2.8 19.5 10.5": ["stat"], "12.0 -1.7 11.2": ["glossy"], "7.4 30.3 -0.5": ["liberated"], "3.6 -1.8 6.4": ["bankruptcies"], "-0.6 6.1 36.8": ["berries"], "23.4 15.0 4.6": ["resurgent"], "10.9 6.4 -1.3": ["resounding"], "10.6 8.7 -3.0": ["fumes"], "7.8 15.9 20.1": ["bark"], "14.0 3.8 22.9": ["jar"], "9.3 8.5 7.4": ["ing"], "5.3 28.2 10.5": ["assailant"], "9.0 8.6 -0.8": ["excesses"], "-4.2 10.4 2.5": ["statistically"], "-2.5 4.7 4.1": ["cricketer"], "9.6 1.2 16.5": ["beads"], "12.5 5.2 16.2": ["fridge"], "1.3 5.1 14.4": ["quilt"], "3.5 3.9 1.0": ["retrial"], "3.0 8.2 14.0": ["temples"], "15.7 29.8 18.6": ["cannon"], "-2.5 26.4 5.0": ["militancy"], "-0.1 14.2 4.9": ["rivalries"], "0.5 10.4 14.8": ["legislatures"], "-2.0 9.5 2.0": ["appellant"], "4.3 10.2 1.6": ["recapture"], "7.1 3.1 2.7": ["fiddle"], "3.3 -0.5 -5.0": ["advancements"], "5.9 20.2 13.8": ["disdain"], "-0.1 11.5 12.2": ["contaminants"], "-0.3 2.1 6.8": ["drawer"], "6.1 8.7 3.6": ["perfume"], "12.0 8.5 28.8": ["fries"], "39.9 13.7 12.8": ["colossal"], "-1.9 4.8 1.2": ["demoted"], "17.5 10.3 4.5": ["transforms"], "4.1 8.3 4.9": ["embankment"], "-5.8 5.5 7.8": ["biking"], "6.8 19.3 5.5": ["blur"], "9.9 13.2 3.8": ["drown"], "-1.6 13.7 -0.7": ["deficiency"], "-0.1 0.7 10.5": ["haircut"], "3.5 11.6 5.1": ["unethical"], "7.5 7.0 3.9": ["equates"], "10.5 -3.2 4.8": ["dampened"], "11.4 5.1 2.2": ["commemorating"], "14.8 8.6 17.2": ["freshly"], "7.7 7.8 7.0": ["amused"], "5.8 9.3 0.1": ["barricades"], "4.5 1.7 3.4": ["calmed"], "-2.2 12.2 2.8": ["ambiguous"], "4.3 9.1 15.9": ["ecology"], "2.6 22.4 6.5": ["fearless"], "0.6 8.0 6.3": ["lineups"], "3.0 17.4 9.1": ["metric"], "10.7 5.7 6.0": ["unease"], "8.9 11.0 12.1": ["rot"], "8.5 12.1 10.0": ["disproportionately"], "16.8 6.4 11.2": ["lump"], "-1.0 18.5 8.1": ["dishonest"], "3.8 3.0 22.7": ["pottery"], "6.7 13.3 13.4": ["frigid"], "2.1 9.1 7.8": ["router"], "22.7 -4.4 7.4": ["aa"], "12.3 27.8 6.9": ["captives"], "14.7 6.0 5.3": ["primed"], "18.6 5.2 8.6": ["hoisted"], "12.1 8.7 11.5": ["bland"], "14.7 4.5 11.8": ["shredded"], "10.3 6.6 3.5": ["smuggle"], "11.9 4.0 5.4": ["poked"], "-3.2 10.5 12.7": ["bikers"], "16.7 19.3 13.0": ["triangle"], "27.7 10.5 2.6": ["futuristic"], "4.2 3.7 12.3": ["illustrations"], "7.4 0.3 -0.6": ["dismisses"], "5.2 14.5 9.3": ["afflicted"], "4.3 2.3 -3.6": ["incorporation"], "10.1 15.7 3.0": ["undeniable"], "-0.3 14.4 9.3": ["majorities"], "18.8 0.8 4.6": ["sleepy"], "-9.6 6.4 7.7": ["songwriting"], "16.6 10.5 -1.4": ["overtaken"], "6.3 5.6 13.5": ["truckers"], "12.9 12.4 16.7": ["sails"], "11.0 1.7 4.3": ["overflowing"], "-1.8 6.9 8.1": ["st"], "22.5 2.5 16.8": ["scraps"], "2.1 7.0 6.3": ["discounting"], "5.7 4.3 8.4": ["contrasts"], "7.7 2.5 14.5": ["cores"], "16.2 4.3 6.9": ["churning"], "1.9 17.3 0.1": ["forcibly"], "9.8 8.7 8.5": ["dictionary"], "3.1 26.1 7.5": ["convoys"], "13.8 12.8 6.5": ["pivot"], "12.1 16.4 13.6": ["decks"], "11.8 10.4 2.3": ["synergy"], "11.8 9.5 16.6": ["hatched"], "4.6 3.9 7.1": ["rowdy"], "9.0 10.2 7.6": ["swagger"], "-3.7 1.1 -1.1": ["compositions"], "22.7 11.1 8.6": ["wielding"], "3.8 21.6 -0.3": ["steadfast"], "-1.3 13.0 6.5": ["acquaintances"], "1.9 10.0 11.8": ["tending"], "12.0 5.3 17.2": ["tagging"], "10.6 3.3 15.0": ["migrating"], "-1.5 -2.6 -2.6": ["groomed"], "0.1 10.1 0.3": ["correcting"], "-2.2 5.5 6.7": ["leeway"], "1.0 12.8 5.9": ["trilogy"], "-3.0 1.3 2.7": ["preclinical"], "6.5 9.1 8.1": ["mapped"], "-2.4 9.3 -7.4": ["recharge"], "1.7 2.3 5.4": ["compliments"], "11.2 21.3 12.7": ["calamity"], "7.2 10.2 1.4": ["fanning"], "-2.0 5.0 1.5": ["choreographer"], "5.7 8.4 5.1": ["pacing"], "-3.2 6.8 6.9": ["untreated"], "11.2 7.8 2.4": ["coolest"], "14.4 15.0 1.2": ["glare"], "1.4 8.3 5.7": ["accumulating"], "6.1 8.7 7.2": ["womb"], "-2.4 4.8 12.4": ["bracelet"], "-5.1 5.8 -0.3": ["diligent"], "-4.7 4.9 32.5": ["meats"], "-1.3 6.2 7.0": ["variance"], "16.2 21.4 0.7": ["blink"], "-3.9 6.2 13.1": ["absentee"], "6.9 5.3 7.0": ["symphony"], "7.6 1.5 9.2": ["jams"], "-1.6 4.4 -1.6": ["disbanded"], "20.0 12.9 26.7": ["rainbow"], "12.5 3.3 23.9": ["juicy"], "2.0 -3.5 4.1": ["smoother"], "-3.1 1.1 1.6": ["pediatrician"], "2.2 9.5 8.5": ["reputations"], "5.8 8.5 2.1": ["apologizes"], "9.4 4.8 1.5": ["caravan"], "-0.2 11.7 6.5": ["morgue"], "8.4 19.1 10.6": ["ridge"], "1.1 9.1 1.0": ["bedside"], "-0.0 6.2 4.2": ["feminine"], "-5.7 13.4 7.8": ["finisher"], "17.8 5.6 -2.5": ["thumping"], "-4.5 -8.6 2.5": ["inquired"], "12.2 10.5 4.6": ["gimmick"], "12.3 25.1 19.3": ["imperial"], "9.1 -2.3 -3.0": ["subpoenaed"], "14.7 10.1 5.6": ["backer", "bodysnatching"], "15.6 22.8 9.5": ["dodge"], "11.1 -4.3 6.6": ["skyrocketed"], "-6.1 3.8 -2.1": ["acquainted"], "7.0 17.9 27.0": ["mosquito"], "6.9 7.2 3.6": ["rousing"], "12.7 7.6 2.9": ["innovators"], "16.8 -5.5 7.8": ["slender"], "4.8 32.0 21.2": ["pests"], "11.0 8.1 6.0": ["scrappy"], "4.8 19.4 4.3": ["illegitimate"], "2.0 14.8 5.4": ["alright"], "5.9 12.2 20.0": ["spinners"], "7.8 2.4 2.6": ["glucose"], "4.7 7.2 3.6": ["workable"], "18.4 30.6 11.9": ["retreating"], "-4.1 -1.4 -2.2": ["solicited"], "11.4 7.5 15.2": ["bumping", "caging"], "-2.8 2.8 7.3": ["epilepsy"], "13.1 2.5 11.9": ["extravagant"], "-3.3 3.9 -2.4": ["unrestricted"], "15.5 4.6 12.4": ["millionaires"], "8.4 6.8 7.2": ["insulated"], "13.0 13.7 8.5": ["shove"], "2.1 13.9 7.5": ["deprive"], "6.8 -0.3 2.1": ["migrated"], "15.8 -6.1 -0.3": ["tout"], "-2.0 5.4 -1.1": ["dehydration"], "11.6 15.2 13.3": ["cardinal"], "7.6 8.4 -0.6": ["interiors"], "5.7 5.5 40.2": ["sushi"], "17.2 11.2 9.9": ["rattle"], "12.6 9.6 4.6": ["stifling"], "6.2 14.3 0.6": ["gunning"], "6.7 1.9 1.3": ["outpaced"], "5.6 25.2 21.9": ["pest"], "6.6 8.7 3.3": ["slums"], "4.8 3.5 11.3": ["welding"], "0.2 1.2 5.0": ["secretariat"], "13.4 7.9 6.6": ["touchscreen"], "3.6 7.4 1.5": ["immersed"], "19.4 9.6 10.7": ["esque"], "3.6 -3.2 10.3": ["dwindled"], "1.1 6.5 10.9": ["netbooks"], "13.0 11.4 14.2": ["terrestrial"], "-1.7 11.3 16.9": ["overboard"], "1.7 11.2 3.6": ["sensed"], "8.2 7.2 7.4": ["faked"], "19.6 -0.8 1.7": ["splashed"], "0.5 -2.5 8.3": ["supplemented"], "13.0 10.2 2.2": ["swarmed"], "10.7 20.1 6.6": ["handler"], "8.9 21.5 3.9": ["ridicule"], "1.5 24.6 0.8": ["fundamentalist"], "1.2 4.7 4.6": ["whistled"], "5.7 -0.2 3.3": ["converge"], "-5.0 -3.0 1.4": ["preside"], "-10.5 9.3 -1.6": ["seminary"], "5.7 6.6 13.1": ["helpers"], "10.7 6.2 0.3": ["reputed"], "-1.7 11.9 -2.2": ["mistreatment"], "26.1 13.4 3.1": ["sucking"], "4.9 3.6 13.2": ["flooring"], "8.1 10.2 -1.7": ["unannounced"], "20.6 4.9 6.3": ["pharma"], "-6.7 2.1 3.6": ["prescribe"], "2.6 7.2 5.2": ["understated"], "-6.2 4.7 2.7": ["misdemeanors"], "-1.1 10.1 4.5": ["comptroller"], "2.8 7.3 0.2": ["passionately"], "-8.6 15.9 -3.3": ["motivating"], "4.9 -8.6 8.4": ["catered"], "3.0 24.5 6.1": ["protagonist"], "1.3 7.2 2.2": ["rectify"], "16.8 6.5 4.0": ["glued"], "16.5 12.1 22.5": ["tails"], "15.0 4.7 3.8": ["valuing"], "5.5 12.6 14.9": ["spyware"], "24.8 8.3 7.7": ["explorer"], "10.4 10.3 2.3": ["heartbeat"], "-5.3 9.3 5.3": ["inexperience"], "-1.4 5.0 3.7": ["culturally"], "9.7 11.0 6.8": ["shattering"], "1.6 9.3 13.6": ["keywords"], "2.3 10.6 16.9": ["keepers"], "5.4 6.1 8.9": ["geology"], "2.6 -0.4 9.0": ["implant"], "-2.2 6.6 -1.3": ["practitioner"], "12.3 12.0 37.7": ["moose"], "2.4 17.7 1.2": ["unseat"], "15.5 30.7 9.4": ["unseen"], "8.9 4.2 3.8": ["ante"], "9.6 8.2 -3.3": ["denouncing"], "2.7 14.7 9.0": ["refueling"], "14.9 18.3 8.5": ["gaze"], "9.6 8.1 5.8": ["fictitious"], "13.2 11.7 17.4": ["limp"], "3.3 7.0 2.0": ["speculating"], "8.6 11.3 6.4": ["antennas"], "8.8 -3.2 -1.1": ["spearheading"], "4.8 2.9 4.0": ["elegance"], "-1.3 5.7 13.5": ["reggae"], "5.6 10.0 6.3": ["unwarranted"], "10.6 12.2 6.1": ["shady"], "-1.6 -0.8 -4.2": ["defaulted"], "5.6 1.8 12.4": ["citywide"], "7.5 1.6 4.6": ["upturn"], "9.2 7.6 4.6": ["astronomers"], "3.2 18.1 4.0": ["injure"], "9.7 3.4 2.7": ["tracing"], "7.8 16.4 -2.8": ["networked"], "7.2 4.0 -0.3": ["thrashed"], "-8.5 -2.1 5.2": ["substitution"], "6.5 1.1 2.0": ["adopts"], "13.4 16.3 5.1": ["beacon"], "-2.4 1.4 6.7": ["concentrates"], "-2.8 -2.2 -1.1": ["dec"], "2.1 4.5 7.1": ["metabolism"], "9.6 2.6 6.9": ["neared"], "19.8 0.6 8.9": ["perched"], "5.4 19.6 5.2": ["infrared"], "1.2 5.6 3.5": ["nudity"], "1.9 10.6 2.2": ["fingertips"], "8.3 15.4 0.1": ["distracting"], "0.6 -5.1 -0.9": ["registrar"], "8.6 3.1 1.6": ["specs"], "31.8 7.9 21.7": ["dinosaur"], "-3.9 3.1 5.0": ["graded"], "1.6 6.9 3.4": ["sixteen"], "12.0 18.0 7.2": ["protectionism"], "13.4 -5.9 10.6": ["wrangling"], "16.3 24.2 2.3": ["silently"], "11.7 -3.2 -1.4": ["donates"], "5.6 7.7 2.1": ["mathematical"], "15.1 7.8 15.2": ["plummet"], "3.2 6.4 -1.7": ["broadest"], "5.4 14.7 -2.4": ["roadblock"], "9.6 3.6 3.7": ["treadmill"], "10.6 17.5 17.9": ["decimated"], "-5.7 10.0 -3.8": ["preached"], "3.9 17.9 6.8": ["painfully"], "7.3 10.2 8.9": ["fatally"], "8.3 11.3 2.5": ["visualization"], "2.2 2.1 14.5": ["transplants"], "-4.5 4.6 11.8": ["sulfur"], "10.7 6.1 -1.8": ["euphoria"], "4.7 4.6 7.8": ["subsided"], "14.3 5.4 18.8": ["donuts"], "13.9 2.2 3.5": ["millennium"], "6.1 7.7 6.9": ["promo"], "15.6 3.2 10.7": ["paltry"], "8.6 9.4 4.9": ["strap"], "-2.7 8.3 19.0": ["dine"], "-4.3 -2.6 -4.8": ["subscribed"], "15.4 6.9 2.5": ["pinnacle"], "1.4 8.8 4.0": ["melodies"], "-6.5 2.2 3.2": ["tryouts"], "9.7 2.4 21.0": ["sludge"], "8.6 -0.6 9.1": ["eases"], "8.2 0.2 7.3": ["peppered"], "5.8 20.7 -1.1": ["mobilizing"], "4.0 11.6 2.0": ["superbly"], "3.0 2.6 -5.0": ["usability"], "-0.8 2.1 12.4": ["beginners"], "14.1 5.4 23.4": ["grease"], "1.9 14.7 6.0": ["inflationary"], "11.3 3.3 10.4": ["auctioneer"], "7.5 1.9 35.7": ["lettuce"], "5.3 17.7 1.0": ["creditor"], "7.8 5.5 1.6": ["pics"], "-2.8 2.6 5.4": ["fashions"], "7.1 2.6 6.1": ["expatriates"], "8.4 28.7 7.5": ["strongholds"], "4.8 9.8 4.1": ["negatively"], "12.6 3.9 11.9": ["layered"], "10.4 4.2 11.3": ["stained"], "-5.7 -0.5 0.1": ["certifications"], "3.4 13.7 12.8": ["antibody"], "2.6 4.3 2.8": ["nightclubs"], "2.2 8.0 7.6": ["inputed"], "6.3 4.0 -0.1": ["reassurance"], "0.2 31.9 3.7": ["oppressed"], "8.2 6.4 6.8": ["subcontractors"], "5.1 9.6 4.7": ["gladly"], "11.1 7.7 10.2": ["anemic"], "7.4 12.0 4.7": ["searchers"], "3.7 6.1 2.3": ["nucleus"], "1.0 6.7 8.6": ["recessions"], "6.7 0.5 -2.0": ["dispel"], "12.1 -3.6 -1.6": ["turnkey"], "4.9 30.5 6.6": ["militiamen"], "5.1 2.9 -3.3": ["publicize"], "5.0 1.9 12.9": ["shoplifting"], "-2.4 3.4 10.2": ["guideline"], "-3.8 -2.2 14.6": ["cookbook"], "-4.5 12.0 2.2": ["indebtedness"], "4.2 15.8 0.3": ["misinformation"], "-4.4 13.2 12.9": ["goalies"], "12.7 10.3 13.8": ["bald"], "5.1 10.1 4.3": ["infuriated"], "5.2 11.8 5.4": ["happiest"], "-0.6 1.6 8.4": ["subscribing"], "0.9 -7.9 1.8": ["lends"], "28.0 11.7 15.4": ["proverbial"], "12.0 10.9 7.4": ["inventive"], "6.3 7.4 1.9": ["adapter"], "1.2 10.2 1.4": ["irritated"], "3.5 -4.5 -5.5": ["auspices"], "15.9 -1.7 4.5": ["skidded"], "15.7 14.0 4.8": ["scarred"], "10.1 7.5 12.6": ["grandma"], "13.0 2.8 18.0": ["biscuits"], "2.0 5.6 11.9": ["campground"], "17.5 12.2 51.3": ["turtle"], "3.2 4.3 22.6": ["manure"], "2.6 15.5 4.6": ["valleys"], "11.1 5.2 0.2": ["sobering"], "6.1 25.2 3.3": ["decisively"], "-5.1 -1.0 -1.5": ["maternity"], "15.6 26.7 8.6": ["savage"], "15.8 6.5 8.5": ["heist"], "9.5 19.0 5.0": ["uphill"], "16.4 39.2 6.0": ["villains"], "13.1 9.1 10.4": ["mounts"], "-1.4 7.3 -7.9": ["misused"], "1.5 12.6 5.9": ["intimacy"], "26.5 9.3 1.2": ["illuminated"], "-0.5 11.3 11.4": ["accession"], "2.2 9.2 2.7": ["sincerely"], "-0.0 9.7 -3.9": ["condone"], "24.5 16.4 3.5": ["circling"], "-1.4 -1.6 3.5": ["invoices"], "3.4 5.4 5.4": ["nicer"], "22.1 8.5 10.1": ["skyline"], "-7.7 13.3 8.6": ["journalistic"], "4.2 20.1 18.2": ["hatch"], "3.1 11.3 -0.1": ["swore"], "7.1 16.1 28.4": ["hull"], "15.8 7.2 11.9": ["brewer"], "-4.5 5.7 13.4": ["vests"], "13.7 10.5 7.0": ["savers"], "-6.0 7.4 6.5": ["alcoholism"], "-5.7 28.5 2.0": ["interrogators"], "3.8 2.2 29.7": ["citrus"], "1.6 4.5 -0.3": ["vindicated"], "11.7 16.2 4.3": ["siren"], "-0.7 0.4 12.0": ["estrogen"], "11.2 18.9 12.8": ["burglar"], "5.0 16.4 5.7": ["agonizing"], "9.4 6.0 1.8": ["unscathed"], "-4.4 -1.6 24.2": ["calves"], "7.2 5.9 9.6": ["claimants"], "15.6 7.9 9.8": ["adorable"], "-0.1 10.4 1.4": ["beatings"], "-9.5 8.8 -2.5": ["unopposed"], "12.0 9.8 9.1": ["prelude"], "9.7 -0.0 8.0": ["fairgrounds"], "12.9 14.1 3.3": ["sweetheart"], "-1.8 13.1 2.2": ["insulted"], "-0.3 7.4 0.6": ["sprints"], "18.3 7.5 14.3": ["goofy"], "10.8 -1.7 7.6": ["hitch"], "-0.2 19.3 5.2": ["occupant"], "-5.2 5.2 -0.1": ["excused"], "-3.5 3.0 31.3": ["fished"], "-2.2 -2.2 -3.8": ["arisen"], "11.4 9.6 5.8": ["ruining"], "-4.0 9.3 5.1": ["superficial"], "2.7 33.3 0.1": ["reconnaissance"], "2.4 10.9 15.9": ["shrubs"], "-5.5 16.0 10.3": ["apprehension"], "9.1 2.0 6.7": ["flourished"], "1.9 -8.6 -0.6": ["petitioned"], "22.9 0.6 -7.4": ["revolutionize"], "-5.6 16.0 4.3": ["confrontations"], "-0.0 3.2 4.2": ["impeccable"], "13.9 8.5 2.0": ["incarnation"], "-2.4 4.0 -1.7": ["happenings"], "6.8 17.6 -3.3": ["extinguish"], "10.6 2.3 5.9": ["decked"], "3.2 11.9 4.8": ["intangibles"], "-0.4 4.4 13.8": ["excavation"], "-5.5 12.8 -3.2": ["truthful"], "0.2 17.6 1.0": ["contradiction"], "-15.2 21.8 -1.2": ["interrogations"], "11.4 9.2 1.3": ["palpable"], "-6.5 15.1 10.4": ["estimation"], "3.3 20.3 3.2": ["paranoid"], "-1.1 9.2 5.9": ["cemeteries"], "6.8 -1.2 4.2": ["bra"], "2.3 1.7 68.1": ["oysters"], "-2.0 7.7 9.0": ["encore"], "10.3 14.1 -0.3": ["overtaking"], "14.0 -1.0 3.9": ["ramped"], "0.5 -2.4 -0.7": ["bps"], "4.9 1.8 -1.4": ["chronicles"], "-1.4 34.1 2.2": ["retaliate"], "9.1 1.4 -2.3": ["pornographic"], "21.4 1.6 9.4": ["frenzied"], "-3.2 6.4 4.2": ["tees"], "11.2 13.5 5.0": ["phenomena"], "9.9 8.3 -2.5": ["redefine"], "2.2 7.6 9.9": ["drinkers"], "5.6 10.3 6.9": ["unruly"], "13.2 1.6 9.9": ["jewel"], "15.8 12.3 15.5": ["smack"], "-7.4 11.5 22.1": ["localities"], "0.7 11.9 1.7": ["solemn"], "2.8 11.4 9.9": ["headlights"], "11.9 12.6 0.5": ["undisputed"], "5.1 5.6 -4.8": ["triumphed"], "9.7 5.0 4.8": ["adjustable"], "11.6 27.4 13.8": ["intruder"], "8.2 18.5 10.3": ["casually"], "17.5 12.6 11.5": ["irresistible"], "18.9 -8.6 4.7": ["cum"], "3.3 9.5 5.3": ["disturb"], "3.0 5.8 13.7": ["wireline"], "14.0 0.6 15.1": ["pony"], "9.8 6.8 -3.3": ["widest"], "18.5 8.1 8.2": ["oddly"], "9.4 6.3 12.2": ["grapple"], "-3.6 0.3 2.8": ["implementations"], "3.1 -3.0 6.5": ["keynote"], "3.7 14.6 4.4": ["sufferers"], "5.6 -0.9 5.5": ["backpacks"], "5.8 19.5 1.2": ["prophet"], "9.5 8.2 7.3": ["shoving"], "-0.5 20.1 6.6": ["gunshot"], "16.3 7.2 7.9": ["stopper"], "7.3 12.9 2.1": ["hotspots"], "8.8 1.8 5.0": ["woven"], "-2.9 12.6 12.8": ["landline"], "12.9 10.0 18.9": ["freezes"], "-3.8 16.8 1.2": ["morally"], "3.0 22.7 4.5": ["interviewer"], "3.9 17.4 7.2": ["emphatically"], "7.0 -3.4 19.7": ["floral"], "6.3 12.4 5.5": ["vibration"], "7.2 34.5 10.2": ["warplanes"], "14.4 6.0 9.9": ["funnel"], "-3.5 1.7 1.4": ["tryout"], "1.6 1.3 0.6": ["max"], "1.0 5.1 0.0": ["notoriety"], "17.3 12.5 7.2": ["swath"], "7.6 4.2 5.7": ["sweepstakes"], "4.5 13.0 3.3": ["evacuating"], "-5.7 15.8 8.4": ["alienated"], "-1.9 2.3 8.8": ["keyed"], "11.0 9.4 11.0": ["straining"], "-4.3 11.1 -2.8": ["dissemination"], "21.3 15.5 3.6": ["pesky"], "6.2 5.0 -1.4": ["resemblance"], "-6.6 5.0 3.8": ["summarized"], "17.6 14.6 9.3": ["spitting"], "-0.3 5.0 1.0": ["instruct"], "8.0 -0.7 -3.4": ["shortlist"], "11.1 4.7 2.4": ["negligible"], "3.2 10.3 6.0": ["choreographed"], "15.0 9.5 28.3": ["edible"], "14.9 6.3 4.5": ["soothing"], "2.8 4.5 -0.1": ["tranche"], "-1.8 3.9 22.0": ["summertime"], "2.4 25.9 15.9": ["gamer"], "7.1 7.3 4.0": ["brightness"], "7.2 11.3 -0.3": ["confines"], "-5.8 2.0 -0.1": ["honorees"], "10.8 4.7 29.6": ["carrots"], "12.4 7.1 -1.3": ["ridiculed"], "-3.1 23.7 5.5": ["counterproductive"], "-4.3 13.4 3.7": ["cadre"], "26.1 6.4 6.5": ["erect"], "7.3 6.3 7.2": ["projector"], "8.2 15.2 4.2": ["awakened"], "-4.5 1.1 23.1": ["compost"], "-7.6 14.0 5.1": ["midfielders"], "10.0 3.6 9.9": ["importation"], "17.2 11.0 3.0": ["outward"], "6.2 1.0 0.6": ["wheelchairs"], "-3.5 -0.8 1.1": ["hitless"], "0.8 1.9 0.3": ["interpreting"], "6.0 39.0 9.4": ["combatants"], "11.4 7.8 15.1": ["skins"], "-6.5 5.4 4.1": ["inflow"], "2.8 10.9 9.1": ["pessimism"], "-2.5 14.3 -1.9": ["manhunt"], "18.6 8.0 14.3": ["crumbled"], "9.3 3.9 10.9": ["graph"], "1.9 -1.4 4.4": ["moot"], "4.0 6.0 10.1": ["sanity"], "-0.9 5.5 3.4": ["academies"], "15.0 11.1 9.5": ["strangely"], "6.9 11.1 6.3": ["sellout"], "3.8 12.7 4.9": ["insensitive"], "18.4 12.7 5.3": ["dummy"], "8.6 -0.5 0.9": ["decried"], "-3.5 45.6 9.3": ["infantry"], "-4.8 6.3 1.8": ["unaccounted"], "-2.3 4.8 7.0": ["bottled"], "6.9 7.7 7.0": ["disappointments"], "7.2 6.4 5.1": ["downsizing"], "5.7 10.9 10.5": ["spoils"], "-4.0 4.9 10.2": ["dietary"], "4.5 -3.5 8.8": ["templates"], "2.7 13.6 11.6": ["potholes"], "-2.7 10.3 13.2": ["euthanized"], "15.6 11.9 8.5": ["woeful"], "2.3 6.3 3.5": ["dilution"], "1.6 12.5 11.0": ["neurons"], "1.4 5.0 7.6": ["reproduced"], "2.1 9.9 -4.0": ["safeguarding"], "8.2 3.1 14.0": ["rubles"], "17.3 9.3 11.5": ["mast"], "2.1 10.9 2.7": ["heirs"], "14.2 6.5 6.0": ["deluge"], "6.6 26.1 16.2": ["caves"], "4.6 14.0 6.1": ["irreversible"], "-2.0 4.3 18.7": ["embryo"], "3.1 15.3 -2.3": ["expel"], "4.8 4.7 2.4": ["restricts"], "2.6 20.2 9.2": ["downfield"], "3.0 11.1 5.3": ["widows"], "16.5 5.4 3.5": ["aisles"], "5.3 5.8 9.2": ["screws"], "3.0 15.0 6.6": ["polio"], "7.7 4.3 6.1": ["dilapidated"], "0.1 11.0 9.4": ["inconsistency"], "-1.3 2.0 5.7": ["evened"], "-5.9 7.8 0.2": ["concise"], "8.5 15.0 2.3": ["thirst"], "1.5 4.9 8.5": ["nicotine"], "9.9 12.1 8.8": ["disappears"], "-2.2 -6.1 -4.2": ["topical"], "2.1 10.8 8.4": ["dialog", "happned", "mep"], "2.7 8.2 5.7": ["undone"], "8.7 18.5 7.4": ["parachute"], "7.1 9.7 0.1": ["overheating"], "2.3 -0.5 0.6": ["abolition"], "9.9 1.7 -0.2": ["droves"], "12.9 9.6 8.2": ["frantically"], "-2.1 3.1 36.8": ["strawberries"], "12.3 7.6 4.4": ["courting"], "6.8 1.9 22.3": ["yogurt"], "6.1 -6.6 11.7": ["cashing"], "-3.3 -0.8 13.3": ["veterinarians"], "7.3 12.8 5.1": ["hedges"], "5.0 -0.3 5.6": ["toned"], "-2.2 -6.1 6.6": ["gowns"], "10.8 13.8 6.0": ["depiction"], "-7.2 10.5 2.1": ["screenwriter"], "11.3 3.7 7.1": ["sandwiched"], "-5.9 8.2 2.1": ["readership"], "5.9 2.3 6.3": ["lingerie"], "1.6 10.8 13.8": ["catchers"], "13.4 2.2 3.1": ["pleads"], "2.1 11.4 4.2": ["unification"], "-4.2 13.7 -0.5": ["excerpt"], "15.6 2.9 13.5": ["braces"], "8.9 12.4 1.0": ["emit"], "-2.5 13.1 9.4": ["melanoma"], "-3.8 33.5 0.6": ["firefight"], "1.6 -4.1 6.4": ["tightness"], "-0.2 6.6 8.2": ["gelding"], "10.5 0.7 13.5": ["trolley"], "21.8 5.7 14.2": ["pyramid"], "4.6 1.6 1.2": ["spasms"], "24.4 -2.2 12.0": ["glittering"], "10.7 4.8 14.7": ["souvenir"], "5.3 2.6 9.0": ["pinning"], "-1.5 -1.8 -2.4": ["sr"], "25.1 -1.5 6.9": ["craze"], "0.5 -3.5 8.7": ["daycare"], "17.0 3.7 6.6": ["outfitted"], "-3.4 11.5 3.3": ["nil"], "3.7 15.4 -0.7": ["mislead"], "15.6 3.3 12.3": ["handouts"], "3.7 8.0 -0.8": ["imprint"], "2.3 8.4 5.6": ["halfback"], "1.3 2.1 5.3": ["tutor"], "9.6 5.1 1.7": ["behest"], "5.2 12.9 16.5": ["sandbags"], "15.9 13.5 3.2": ["beware"], "-7.2 4.2 -4.5": ["inconsistencies"], "10.5 3.3 8.5": ["bathtub"], "4.3 1.4 2.8": ["bylaws"], "9.4 4.2 4.0": ["coined"], "-2.7 18.1 8.1": ["animosity"], "10.8 4.5 1.1": ["spearhead"], "7.2 2.6 2.3": ["constitutionality"], "-2.1 2.7 1.4": ["sociology"], "-5.9 3.0 9.2": ["remittances"], "-3.4 6.6 -1.2": ["reassigned"], "8.7 2.3 5.1": ["clamoring"], "12.3 13.2 6.6": ["sharpest"], "7.5 6.7 2.5": ["behaving"], "3.0 14.3 24.2": ["waterway"], "10.6 19.6 7.3": ["misfortune"], "6.9 6.3 0.3": ["calculates"], "4.9 4.8 16.7": ["mustache"], "14.5 4.8 10.6": ["diva"], "10.4 -0.9 7.1": ["flex"], "1.4 0.7 6.7": ["preserves"], "4.9 4.3 2.1": ["tearful"], "-3.2 6.0 2.1": ["zoned"], "5.1 1.6 1.5": ["bridging"], "-0.2 7.5 4.1": ["invoke"], "8.3 6.2 4.1": ["coatings"], "15.9 12.2 7.0": ["arch"], "-3.0 3.6 -2.8": ["underserved"], "12.5 14.3 12.0": ["lasers"], "-4.4 16.4 3.1": ["combative"], "14.5 27.2 7.9": ["damned"], "10.9 4.3 -0.7": ["defraud"], "15.9 -2.4 7.8": ["yanked"], "-0.8 12.7 3.8": ["verbally"], "-0.8 1.7 2.7": ["showings"], "-0.1 9.1 0.3": ["unresponsive"], "3.3 10.4 18.1": ["cigar"], "2.9 4.3 -3.0": ["differentiated"], "1.9 10.9 6.1": ["overriding"], "3.5 6.3 3.8": ["honed", "elocution"], "17.5 15.7 11.1": ["geek"], "5.9 7.9 5.9": ["attachments"], "2.1 3.5 8.9": ["percussion"], "-5.6 3.2 2.1": ["unsolved"], "2.2 5.6 0.6": ["arbitrator"], "-7.7 4.8 6.4": ["schooled"], "1.3 -2.4 0.1": ["concurrently"], "-0.1 9.5 15.5": ["grilling"], "27.3 15.5 14.9": ["wizard"], "-0.1 6.2 12.3": ["scooter"], "14.7 4.4 3.6": ["whistles"], "16.2 3.2 -0.3": ["writedowns"], "-2.3 -7.3 11.1": ["adoptions"], "7.8 -0.5 26.4": ["specimens"], "2.6 14.3 14.9": ["replenish"], "-4.0 14.8 3.1": ["headset"], "15.3 2.2 11.1": ["robotics"], "3.8 3.2 15.2": ["silverware"], "12.7 -3.7 14.5": ["snagged"], "-9.8 8.4 5.6": ["punishments"], "5.6 11.8 7.9": ["wastes"], "6.4 3.4 10.3": ["nuns"], "-0.6 7.3 -3.2": ["dossier"], "9.2 -1.8 -4.6": ["secures"], "-13.2 5.6 13.0": ["furlough"], "12.8 19.0 11.5": ["mafia"], "10.8 7.2 3.7": ["sigh"], "7.6 13.3 22.1": ["quarry"], "9.0 10.1 6.1": ["etched"], "6.0 3.2 11.2": ["entitlements"], "5.2 6.1 8.2": ["dunks"], "-2.8 9.4 2.7": ["mutations"], "-4.6 4.5 7.5": ["appropriated"], "5.4 11.2 22.3": ["moist"], "8.8 2.9 19.7": ["mint"], "-10.8 3.2 13.9": ["furloughs"], "7.3 11.0 5.3": ["hangar"], "0.6 11.0 0.8": ["flattering"], "4.1 9.3 8.2": ["ankles"], "0.3 18.4 27.0": ["foliage"], "11.7 -1.8 5.0": ["spurring"], "13.4 0.7 9.1": ["quaint"], "13.1 1.1 5.0": ["outweighed"], "7.1 15.2 6.7": ["sharpen"], "9.7 8.2 14.0": ["smog"], "-1.0 0.5 0.5": ["autographs"], "26.1 4.5 4.7": ["czar"], "-4.6 10.1 16.9": ["winters"], "14.0 1.0 -2.7": ["revamping"], "6.5 8.7 3.7": ["scroll"], "5.2 16.0 9.9": ["unprepared"], "1.0 -2.7 7.3": ["archiving"], "5.7 6.8 19.2": ["liners"], "-4.8 0.4 2.0": ["escrow"], "-4.7 -0.7 11.2": ["ticketed"], "5.4 3.2 -5.0": ["rejoined"], "1.2 7.2 6.9": ["interrupt"], "8.8 17.0 10.2": ["dread"], "7.3 29.1 6.1": ["bunkers"], "10.8 0.4 9.2": ["padded"], "0.4 17.5 5.8": ["taboo"], "17.0 4.5 0.7": ["overhauling"], "1.5 0.9 12.9": ["berths"], "14.6 18.0 2.8": ["boldly"], "12.4 2.0 7.7": ["quasi"], "8.6 2.7 10.6": ["shale", "seasonlong"], "-1.1 6.3 -0.0": ["onus"], "8.9 1.1 10.0": ["demos"], "6.3 13.1 1.6": ["exhilarating"], "5.8 8.9 13.5": ["overlapping"], "-1.5 13.6 7.1": ["infighting"], "13.0 24.6 11.6": ["lest"], "-1.3 3.1 7.8": ["scarves"], "-0.7 -3.8 7.0": ["envelopes"], "1.6 7.3 12.6": ["savor"], "-2.2 8.0 5.7": ["sportsmanship"], "4.1 0.7 7.4": ["tweaking"], "1.1 4.8 0.9": ["anomalies"], "12.9 4.7 0.9": ["overstated"], "3.9 14.5 16.9": ["brew"], "12.2 1.5 4.0": ["hangover"], "-1.3 23.0 2.0": ["infiltration"], "-9.7 0.9 4.7": ["retirements"], "8.8 18.0 3.0": ["sneaking"], "12.7 1.8 3.7": ["shoddy"], "7.9 6.9 5.4": ["restless"], "6.9 17.2 1.8": ["fateful"], "13.9 13.4 0.7": ["proclaiming"], "1.5 17.7 4.9": ["purposely"], "2.7 5.1 0.2": ["showrooms"], "0.2 0.7 1.7": ["channeled"], "1.7 6.6 -3.7": ["simplifying"], "-3.0 28.9 4.6": ["colonel"], "0.4 15.3 7.0": ["unwillingness"], "3.9 8.3 3.8": ["hurried"], "4.8 6.5 6.8": ["nervousness"], "5.0 6.9 1.7": ["undue"], "-0.7 -0.8 -4.6": ["endorses"], "8.3 7.2 2.1": ["maths"], "14.2 5.5 9.4": ["celebratory"], "10.3 31.6 3.7": ["murderous"], "9.0 10.7 8.0": ["breaker"], "16.4 38.1 5.8": ["stealth"], "3.4 20.4 9.9": ["narrator"], "11.7 4.1 5.3": ["jittery"], "14.6 1.9 4.8": ["dispensing"], "5.5 -4.5 -2.6": ["scrutinize"], "9.2 10.3 7.3": ["mockery"], "11.6 24.0 4.3": ["unmanned"], "5.8 14.3 7.1": ["dribble"], "15.2 0.5 -0.3": ["underscoring"], "-4.2 9.2 3.8": ["valuables"], "6.4 11.3 2.7": ["grouped"], "14.3 12.8 1.8": ["beaming"], "7.7 -2.6 0.3": ["majoring"], "4.2 3.5 9.1": ["grounding"], "2.7 17.6 -1.7": ["trustworthy"], "7.9 2.8 8.8": ["legalize"], "3.2 -8.9 2.6": ["administers"], "1.8 10.0 9.4": ["creatively"], "5.2 16.2 5.6": ["avoidance"], "4.8 1.0 1.5": ["replicated"], "4.7 8.4 5.7": ["begs"], "10.6 13.1 6.8": ["overwhelm"], "1.1 2.2 -4.0": ["embodies"], "2.3 3.5 16.0": ["postgame"], "9.7 6.5 11.0": ["cashier"], "8.7 1.9 12.7": ["cloning"], "3.3 16.0 4.2": ["preferable"], "11.5 20.2 3.2": ["fortified"], "11.4 10.8 7.6": ["marchers"], "0.2 12.0 11.8": ["occupations"], "8.0 3.4 6.0": ["polymer"], "5.2 -2.5 6.7": ["registers"], "6.3 8.8 5.1": ["nearer"], "0.6 9.3 5.2": ["trainees"], "10.0 9.7 2.3": ["missteps"], "-5.3 -2.5 0.0": ["alterations"], "14.9 20.3 7.2": ["idiots"], "3.0 10.4 4.1": ["heater"], "5.3 14.8 1.4": ["summon"], "1.6 8.0 -3.9": ["predictive"], "7.7 11.5 10.2": ["fleeting"], "3.4 6.1 8.5": ["cheerleading"], "5.0 9.9 1.6": ["blacked"], "7.4 15.9 9.7": ["thrives"], "12.1 9.8 2.9": ["beamed"], "2.9 8.8 2.2": ["derogatory"], "0.0 6.9 6.2": ["meticulous"], "-2.5 9.1 0.3": ["contradict"], "3.5 10.8 1.6": ["substation"], "7.6 10.4 5.9": ["filthy"], "-0.9 15.2 1.7": ["thinkers"], "8.9 10.9 7.7": ["sighting"], "9.3 0.6 -3.1": ["underlines"], "-0.3 8.7 10.1": ["motorbike"], "7.0 3.3 -5.3": ["insolvency"], "-8.0 6.6 12.9": ["superintendents"], "16.3 6.0 6.8": ["plume"], "5.4 2.1 4.5": ["grossed"], "-3.1 -4.7 2.9": ["rescinded"], "-4.9 1.6 20.2": ["brunch"], "3.2 11.7 2.1": ["convincingly"], "2.1 8.3 8.6": ["repurchased"], "6.0 14.8 6.0": ["notions"], "5.9 1.9 2.6": ["cleaners"], "3.1 2.4 5.1": ["regents"], "5.5 7.6 2.2": ["restrooms"], "2.8 16.4 -4.2": ["complicity"], "8.5 13.5 -0.4": ["deflect"], "0.2 8.0 9.6": ["farmhouse"], "3.6 15.8 9.8": ["needless"], "6.8 -0.7 10.4": ["expatriate"], "9.6 2.2 7.2": ["commemorative"], "14.0 27.3 7.7": ["scourge"], "13.7 14.0 1.8": ["collide"], "5.9 1.2 5.9": ["disclaimer"], "8.4 13.3 4.8": ["purge"], "0.2 -7.0 5.2": ["syndication"], "8.5 13.9 0.6": ["unbeatable"], "3.4 1.0 14.3": ["undergraduates"], "0.2 2.1 1.1": ["attest"], "12.4 7.6 8.0": ["necks"], "11.7 -0.4 -1.8": ["ancillary"], "4.1 5.2 5.6": ["thru"], "8.5 11.4 4.7": ["writ"], "5.4 4.9 28.7": ["bison"], "-4.8 6.6 5.1": ["departmental"], "10.0 19.9 3.7": ["disable"], "0.9 3.7 -2.2": ["profiling"], "5.8 10.2 7.0": ["footy"], "16.6 7.8 -2.7": ["inventions"], "-7.2 2.2 9.2": ["transient"], "-8.7 -0.7 -0.8": ["remand"], "6.1 14.4 4.7": ["ailment"], "-8.0 7.9 9.3": ["backstroke"], "11.8 13.7 5.1": ["bloodied"], "20.1 11.6 12.1": ["majestic"], "8.0 9.3 14.2": ["plowing"], "6.5 1.7 -0.3": ["faulted"], "3.6 20.0 3.9": ["victor"], "1.2 1.9 7.0": ["normalcy"], "26.8 2.5 18.0": ["faux"], "-2.4 2.9 -3.2": ["circulate"], "-1.8 1.9 1.5": ["hrs"], "7.4 14.5 10.5": ["wakes"], "2.2 6.7 6.6": ["substandard"], "-4.4 13.6 2.3": ["conditioned"], "15.3 19.6 2.8": ["unimaginable"], "-3.3 3.5 11.3": ["painkillers"], "2.0 4.7 0.7": ["enshrined"], "14.2 5.3 3.2": ["bulky"], "10.4 7.2 8.4": ["unregulated"], "10.3 14.2 1.3": ["unlawfully"], "-5.9 1.5 0.9": ["transpired"], "5.4 13.2 1.0": ["strife"], "9.2 7.0 14.6": ["fertile"], "14.8 7.5 4.7": ["hurling"], "14.2 1.6 4.1": ["glitches"], "2.8 0.5 6.4": ["earners"], "12.5 6.7 0.1": ["queues"], "7.7 8.9 12.0": ["ridiculously"], "19.9 13.5 2.0": ["ingenuity"], "13.4 0.6 7.5": ["storefront"], "2.4 6.0 3.5": ["perpetuity"], "5.3 2.9 2.2": ["aesthetics"], "1.4 11.1 4.2": ["lateral"], "-2.6 -0.2 9.8": ["reimbursements"], "5.9 14.0 9.4": ["decay"], "1.4 6.5 2.3": ["reshuffle"], "3.0 25.5 6.0": ["brutally"], "4.6 20.2 3.2": ["unbearable"], "10.4 3.7 8.9": ["soaking"], "4.0 2.1 6.5": ["newborns"], "3.4 7.9 -1.2": ["denials"], "6.4 7.1 2.6": ["catchy"], "6.1 14.9 5.6": ["outnumbered"], "2.2 16.9 2.3": ["selectively"], "3.6 10.7 7.5": ["cures"], "4.2 7.6 2.5": ["ethos"], "4.0 1.1 1.6": ["handwritten"], "2.1 5.7 2.5": ["coughing"], "24.0 36.1 9.0": ["superpower"], "8.2 3.2 14.2": ["bikini"], "1.0 1.8 7.4": ["malpractice"], "10.8 10.7 5.0": ["quantum"], "6.5 19.9 15.4": ["blight"], "3.6 6.5 1.8": ["articulated"], "3.1 11.6 2.2": ["undetermined"], "15.7 17.4 7.0": ["swoop"], "9.0 13.1 21.6": ["typhoon"], "4.3 21.7 4.6": ["bluntly"], "1.3 13.7 1.6": ["distortion"], "6.6 4.5 7.4": ["rubbed"], "3.5 9.8 4.2": ["scratches"], "12.7 -0.8 7.6": ["catwalk"], "5.3 13.0 2.1": ["decider"], "7.3 9.4 11.4": ["sublime"], "-0.2 1.3 -2.2": ["notifications"], "6.8 8.2 18.1": ["pint"], "-2.8 11.9 -2.7": ["annexed"], "16.0 15.4 23.4": ["rotten"], "8.2 10.8 3.7": ["startled"], "19.0 1.8 14.3": ["rosy"], "18.7 2.6 9.3": ["dangling"], "-1.3 5.6 4.2": ["birthdays"], "8.2 6.5 8.0": ["limping"], "5.4 6.1 4.9": ["buckle"], "4.5 15.0 7.8": ["anarchy", "maama"], "-3.1 4.5 3.0": ["toxicity"], "2.0 24.4 3.4": ["despicable"], "3.0 20.7 10.5": ["separatists"], "15.0 5.2 5.1": ["calculator"], "2.4 10.6 8.4": ["saint"], "-3.7 7.7 7.9": ["juncture"], "-0.0 26.8 4.8": ["murderers"], "-6.8 16.0 8.9": ["morals"], "1.8 4.8 5.4": ["introductions"], "5.7 8.1 7.5": ["algorithm"], "5.2 14.8 2.5": ["tenacity"], "-0.7 9.4 9.6": ["roommates"], "-1.1 4.8 10.2": ["countywide"], "5.8 5.1 2.2": ["greets"], "10.1 5.5 1.8": ["withstood"], "-0.3 8.4 5.7": ["interruptions"], "11.8 5.3 -4.3": ["damning"], "5.8 17.4 5.8": ["burglars"], "-0.5 17.0 12.0": ["conservatism"], "-8.2 5.3 5.0": ["anesthesia"], "4.0 6.7 18.1": ["immature"], "-7.1 10.5 7.7": ["forex"], "4.5 14.9 2.3": ["unify"], "4.8 22.2 -3.1": ["marshal"], "11.1 3.2 14.2": ["simmering"], "3.8 16.7 13.7": ["mistrust"], "15.0 16.4 4.7": ["crawled"], "8.2 -0.6 1.9": ["cusp"], "9.2 -6.7 6.7": ["yr"], "7.3 0.8 8.5": ["disks"], "1.9 16.1 15.0": ["gangster"], "19.6 19.1 3.2": ["unleashing"], "4.4 9.4 9.5": ["hampering"], "7.3 17.1 7.2": ["stain"], "13.8 -10.3 5.0": ["ballooned"], "-1.0 11.9 4.2": ["hone"], "5.6 1.5 -1.4": ["originate", "acording"], "-1.3 21.4 8.8": ["liberties"], "8.1 6.7 11.4": ["chew"], "-5.4 4.1 7.6": ["deem"], "1.7 7.4 4.7": ["socialize"], "21.0 11.3 7.9": ["pummeled"], "11.2 12.0 11.5": ["bows"], "2.1 0.2 3.2": ["equestrian"], "10.5 4.7 6.0": ["midsize"], "-0.3 7.7 -0.6": ["frees"], "9.6 16.4 19.5": ["mustard"], "17.4 6.0 12.8": ["flourishing"], "-5.3 16.5 12.8": ["changeup"], "5.3 14.6 -1.9": ["inaccessible"], "7.0 -7.3 9.2": ["fetched"], "1.0 9.3 2.1": ["nurtured"], "13.1 6.2 5.3": ["trump"], "-0.8 12.6 1.1": ["enlightened"], "-1.6 -0.2 3.1": ["expedited"], "20.6 4.6 2.0": ["movers"], "-3.4 8.0 9.0": ["temperament"], "4.9 7.1 2.5": ["undeveloped"], "4.2 2.9 9.8": ["milling"], "-9.7 -4.3 10.0": ["pregnancies"], "6.9 5.3 28.9": ["pies"], "13.9 8.8 9.2": ["wayward"], "8.9 8.9 21.4": ["waiter"], "4.1 11.7 17.1": ["skater"], "11.3 6.8 32.5": ["coconut"], "3.2 -4.9 7.3": ["implants"], "-4.8 1.5 -3.0": ["garnering"], "-0.7 25.9 8.1": ["shrapnel"], "7.2 31.4 6.8": ["communists"], "4.4 4.7 5.4": ["contrasting"], "-0.7 2.7 11.3": ["inn"], "16.7 -0.5 7.9": ["dented"], "14.0 9.3 -2.9": ["overtook"], "8.2 24.4 8.2": ["stupidity"], "3.8 7.7 19.7": ["yachts"], "0.1 5.0 -3.5": ["intersected"], "0.3 0.2 6.5": ["autographed"], "-0.7 3.0 6.1": ["deducted"], "16.2 27.1 2.1": ["conquered"], "10.0 17.8 11.9": ["hides"], "6.5 26.8 7.9": ["incursion"], "8.0 14.1 29.1": ["tides"], "5.7 14.6 3.6": ["maverick"], "2.4 11.6 -2.5": ["discredited"], "5.0 10.7 10.1": ["clueless"], "0.8 2.5 4.5": ["enactment"], "-6.8 12.3 15.2": ["antibiotic"], "11.5 6.8 -2.0": ["untapped"], "5.0 6.2 1.0": ["procure"], "9.5 32.3 7.5": ["drones"], "-10.3 -0.8 1.1": ["differed"], "-5.8 12.7 -2.7": ["compromising"], "4.8 12.6 11.4": ["foursome"], "7.4 20.5 7.3": ["inclination"], "-1.6 13.0 10.0": ["interleague"], "2.6 13.6 -1.7": ["tiring"], "14.0 11.6 -1.3": ["hijack"], "-5.2 9.6 11.4": ["foreclosed"], "2.8 5.2 -5.7": ["paces"], "5.8 -1.0 4.4": ["alum"], "1.2 9.5 4.7": ["eighteen"], "8.9 18.4 10.3": ["traffickers"], "10.1 12.2 8.2": ["oblivious"], "3.5 0.9 11.1": ["batches"], "9.0 1.1 11.7": ["lorry"], "14.9 -0.2 -0.8": ["graced"], "5.1 6.6 3.2": ["trainee"], "7.6 13.5 35.7": ["geese"], "9.5 5.4 9.6": ["pillows"], "11.3 -2.3 4.6": ["en"], "9.4 3.8 8.9": ["walkway"], "4.3 19.6 9.6": ["mischief"], "12.0 15.9 10.6": ["backside"], "1.8 15.1 4.7": ["presumption"], "11.4 3.0 -0.7": ["overhauled"], "-0.0 12.8 30.7": ["grape"], "2.7 16.6 15.9": ["cynicism"], "8.2 18.8 0.2": ["infiltrated"], "5.8 11.1 43.6": ["reef"], "4.6 24.3 5.1": ["countrymen"], "1.9 6.2 23.0": ["syrup"], "6.3 13.8 7.8": ["apathy"], "10.1 10.5 26.2": ["eagles"], "12.9 13.3 7.2": ["pretended"], "-4.8 10.7 -1.3": ["facilitator"], "-5.3 19.3 6.9": ["republican"], "4.7 13.3 -4.6": ["telephones"], "15.5 7.4 17.8": ["unloading"], "14.6 15.4 11.3": ["restive"], "6.1 17.6 7.0": ["provoking"], "-5.8 7.1 6.5": ["fasting"], "-2.4 7.4 13.8": ["skis"], "11.1 -3.8 3.1": ["compressed"], "9.7 4.1 9.5": ["accelerator"], "-5.1 8.3 5.9": ["differentiation"], "5.4 1.5 3.1": ["swerved"], "-1.0 11.6 9.4": ["nuances"], "23.1 3.7 -2.5": ["bn"], "11.3 6.9 5.1": ["trumped"], "10.0 15.9 12.6": ["unjustified"], "6.5 6.1 5.7": ["motorway"], "2.4 12.3 6.7": ["scar"], "20.7 11.7 15.7": ["shelled"], "3.5 2.3 0.2": ["unproven"], "1.9 7.3 6.6": ["folders"], "6.6 2.8 13.4": ["ringgit"], "8.4 27.3 9.1": ["populace"], "3.9 11.7 1.3": ["transmissions"], "1.7 9.4 6.2": ["scalp"], "15.1 5.8 1.1": ["malfunction"], "5.8 10.6 16.4": ["surfer"], "14.7 9.8 16.5": ["drags"], "6.5 4.9 6.7": ["railing"], "-3.9 3.7 5.8": ["appellate"], "1.9 2.6 12.9": ["legalized"], "1.6 26.7 10.9": ["bigotry"], "-2.8 16.2 10.0": ["banter"], "5.1 22.3 12.9": ["foreigner"], "-3.5 9.2 6.7": ["latitude"], "-5.3 7.7 4.2": ["effected"], "-3.7 3.5 11.2": ["viewership"], "9.4 9.2 7.3": ["vigor"], "16.4 11.8 38.1": ["alligator"], "5.4 1.0 -2.6": ["probed"], "-2.6 10.2 2.7": ["disillusioned"], "7.6 -6.8 10.4": ["sa"], "3.3 8.4 4.7": ["equate"], "4.5 8.6 0.5": ["expressly"], "-3.8 6.5 10.0": ["repatriation"], "23.4 7.0 1.2": ["financier"], "-4.7 -2.3 3.8": ["busier"], "-4.4 10.7 -2.8": ["instill"], "7.4 8.8 5.4": ["tabloids"], "4.1 -0.4 6.3": ["dearth"], "-4.4 6.9 -2.5": ["affiliations"], "-1.4 3.9 -0.4": ["greetings"], "11.7 10.7 18.0": ["vanilla"], "5.3 26.2 7.9": ["warlords"], "11.3 5.3 0.1": ["downgrades"], "-11.0 9.0 4.5": ["ordained"], "4.6 21.5 9.4": ["germs"], "-4.2 20.4 6.5": ["motivations"], "2.2 23.3 1.6": ["arming"], "19.5 -5.0 7.6": ["ditched"], "5.5 10.9 8.2": ["draconian"], "7.5 23.4 11.3": ["cursed"], "34.1 24.3 35.8": ["dragon"], "-10.4 2.8 2.2": ["manuscript"], "15.7 19.2 4.6": ["unrelenting"], "1.0 8.0 3.4": ["inhibit"], "4.8 10.2 26.3": ["poaching"], "4.6 -1.6 -4.3": ["eminent"], "14.7 9.3 -2.1": ["simulator"], "-6.4 0.2 11.7": ["duplex"], "2.0 8.2 7.9": ["consummate"], "-0.3 -0.0 -9.7": ["optioned"], "-0.5 13.2 -0.0": ["retake"], "8.6 6.3 0.5": ["letdown"], "9.5 3.4 9.2": ["speedway"], "27.5 14.2 41.6": ["frog"], "-0.9 7.8 15.3": ["wagering"], "13.9 -0.7 5.2": ["aborted"], "0.1 15.2 11.6": ["bookies"], "4.7 -0.9 1.4": ["rollover"], "-6.4 8.0 -5.0": ["contradicted"], "2.3 6.3 15.6": ["undocumented"], "7.0 0.9 6.5": ["puzzling"], "12.8 8.9 14.8": ["penis"], "1.8 6.1 4.9": ["wrists"], "0.5 6.6 3.0": ["retrospect"], "9.3 3.1 4.3": ["pondering"], "7.1 7.5 6.5": ["convicts"], "0.8 5.6 3.7": ["authorizes"], "14.3 7.6 3.6": ["miraculous"], "-9.4 1.3 3.5": ["deliberation"], "2.1 0.7 10.1": ["finer"], "-0.0 6.4 2.2": ["transitioning"], "5.6 8.5 4.1": ["circumvent"], "-1.8 5.6 -0.1": ["persuasive"], "-1.4 10.4 1.2": ["overheard"], "13.3 7.1 4.0": ["erasing"], "1.7 12.8 14.0": ["wrecks"], "-1.8 27.6 -3.2": ["assassinate"], "12.3 11.4 3.5": ["den"], "-5.3 2.7 6.4": ["disqualification"], "3.0 -1.2 2.0": ["mattresses"], "8.3 5.6 3.9": ["calming"], "17.5 13.9 11.9": ["poke"], "10.8 -4.4 -2.9": ["resurfaced"], "15.5 3.7 5.4": ["loom"], "8.2 19.3 -1.0": ["irritating"], "7.7 10.1 10.8": ["spotty", "reflation"], "9.4 20.9 0.3": ["horrifying"], "3.0 6.2 7.3": ["tenuous"], "4.5 12.3 2.8": ["microphones"], "-8.2 14.3 9.1": ["contingencies"], "2.8 0.4 9.0": ["handbag"], "25.5 9.9 3.8": ["billionaires"], "-0.9 1.0 2.5": ["leniency"], "7.0 2.5 1.5": ["biometric"], "-3.8 6.8 5.8": ["nods"], "11.4 11.7 49.0": ["catfish"], "5.9 12.7 6.4": ["mastery"], "-0.2 12.6 6.1": ["chlorine"], "5.3 3.5 7.1": ["invoice"], "9.2 7.1 14.9": ["scissors"], "12.0 20.0 9.8": ["imaginable"], "12.5 2.8 4.4": ["francs"], "-3.2 17.1 7.1": ["debtor"], "12.9 8.7 11.5": ["hydraulic"], "-3.1 9.5 2.2": ["attentive"], "4.0 23.8 8.1": ["illusions"], "3.0 10.7 -2.0": ["intermediary"], "16.6 -0.3 5.3": ["lagged"], "6.9 6.3 3.0": ["dilute"], "-0.3 2.1 8.1": ["allocating"], "2.6 13.1 2.5": ["legitimately"], "9.4 21.6 7.9": ["emboldened"], "21.2 10.4 7.0": ["marvel"], "-1.2 13.1 -3.1": ["advantageous"], "9.5 9.5 -1.2": ["acronym"], "2.7 0.9 9.9": ["culled"], "11.0 -4.1 8.4": ["underpinned"], "7.2 8.5 8.9": ["joyous"], "4.1 14.4 0.2": ["incompatible"], "6.8 1.9 7.7": ["sewing"], "-5.5 4.9 3.6": ["pts"], "-6.2 9.2 21.4": ["regatta"], "9.6 2.5 3.9": ["copyrighted"], "2.9 6.3 13.9": ["chocolates"], "4.5 13.9 0.9": ["forgiving"], "17.3 22.7 9.5": ["poisonous"], "7.5 16.0 4.4": ["pixels"], "0.7 6.9 1.1": ["respondent"], "18.3 -0.1 12.9": ["circa"], "13.2 6.1 28.6": ["pine"], "6.5 7.6 16.7": ["canals"], "1.6 11.9 12.9": ["unanticipated"], "7.1 11.6 8.7": ["handshake"], "-6.2 2.0 -1.7": ["elective"], "-5.9 5.4 -3.2": ["confessions"], "7.0 4.9 8.3": ["fenced"], "10.1 10.5 2.9": ["disposing"], "6.7 6.7 8.9": ["stormy"], "10.4 5.6 -0.6": ["boosters"], "-1.0 4.8 -0.4": ["wellbeing"], "3.3 18.2 5.2": ["admirers"], "7.8 10.3 29.5": ["shipyard"], "1.0 15.0 2.8": ["weakens"], "8.6 14.1 12.1": ["predictably"], "-0.5 1.5 -7.2": ["commendable"], "3.9 3.1 3.3": ["breather"], "13.0 16.1 28.9": ["spawn"], "5.4 13.3 0.4": ["proclaim"], "4.3 13.9 8.5": ["unbelievably"], "5.8 5.3 6.7": ["springboard"], "16.9 8.9 4.2": ["drenched"], "3.9 6.8 -2.7": ["initials"], "8.6 17.9 4.0": ["simplistic"], "2.0 4.7 11.2": ["dislocated"], "8.1 -1.3 6.6": ["shaving"], "4.1 8.2 2.0": ["hinting"], "18.3 3.6 7.7": ["spooked"], "0.6 -1.1 3.9": ["supplementary"], "8.3 -0.2 14.1": ["federally"], "9.0 14.4 1.6": ["reorganize"], "13.2 13.4 10.1": ["hover"], "-2.9 13.2 4.6": ["reconciled"], "0.4 15.0 7.5": ["rightfully"], "11.3 6.1 4.4": ["falter"], "11.7 4.8 9.1": ["dumps"], "-5.1 6.1 6.3": ["vacationing"], "6.3 4.9 -1.9": ["duped"], "6.9 4.3 1.2": ["gutsy"], "-6.5 21.4 2.8": ["accomplishing"], "-7.7 3.8 1.2": ["medically"], "6.3 8.7 16.4": ["thaw"], "0.6 7.3 9.8": ["corrosion"], "6.7 7.9 11.2": ["larceny"], "17.0 7.4 12.4": ["canopy"], "5.4 20.1 26.9": ["landings"], "5.4 5.3 5.6": ["aldermen"], "21.7 -0.3 5.9": ["awash"], "9.8 4.3 9.4": ["budge"], "2.2 11.6 11.0": ["luckily"], "1.4 11.8 0.3": ["geographically"], "5.0 11.4 13.7": ["landowner"], "8.9 2.7 10.6": ["leaner"], "15.5 2.6 24.5": ["carrot"], "0.2 13.4 -0.8": ["partition"], "13.5 2.8 5.4": ["reaping"], "9.7 4.6 21.7": ["hearty"], "5.2 14.8 4.7": ["unscrupulous"], "5.6 8.9 8.5": ["teased"], "3.3 5.5 6.0": ["orphaned"], "26.5 11.4 3.4": ["upstart"], "5.5 1.8 0.5": ["solvent"], "6.5 9.1 -2.3": ["drubbing"], "-0.8 4.8 6.9": ["mudslides"], "1.1 10.8 5.9": ["prevails"], "-3.1 10.8 7.1": ["takedown"], "2.0 4.2 -1.0": ["portability"], "-3.3 0.2 11.6": ["triathlon"], "9.0 3.3 -1.8": ["seater"], "-0.9 4.8 9.7": ["enacting"], "0.0 24.4 0.9": ["accomplices"], "10.5 4.2 3.2": ["chiefly"], "6.4 0.7 0.9": ["renegotiate"], "6.3 2.6 15.9": ["ceramics"], "-0.7 3.8 9.9": ["outbound"], "-7.6 7.0 2.5": ["clinically"], "16.3 14.0 7.6": ["trillions"], "9.0 -2.9 8.7": ["lingered"], "1.8 2.2 5.8": ["redress"], "16.8 18.8 8.1": ["cripple"], "11.2 -1.4 -1.5": ["lifespan"], "1.2 8.3 1.0": ["covenant"], "0.5 3.9 15.2": ["arsenic"], "3.9 8.4 3.2": ["deems"], "2.0 30.6 11.2": ["perpetrator"], "7.0 2.1 0.7": ["broadened"], "26.2 8.4 3.2": ["takeovers"], "3.9 9.8 0.3": ["pursues"], "10.0 5.1 5.0": ["exploratory"], "-10.4 10.3 2.2": ["rapport"], "-2.3 17.8 2.0": ["repetition"], "18.5 4.1 3.7": ["bowing"], "2.0 8.9 3.3": ["braved"], "8.0 5.3 5.5": ["onerous"], "12.2 12.4 -2.4": ["railroads"], "7.0 12.8 12.8": ["endemic", "cherie"], "8.4 9.4 8.5": ["grandstand"], "8.8 5.5 4.2": ["checkout"], "9.2 21.5 13.8": ["loot"], "-2.4 4.7 -0.5": ["revaluation"], "5.1 1.1 16.8": ["lace"], "-7.4 10.8 1.8": ["memoirs"], "5.2 16.4 9.1": ["payload"], "3.5 17.4 5.4": ["sacrificing"], "16.2 3.7 13.1": ["rake"], "8.6 8.4 -5.4": ["licensee"], "1.4 2.6 2.0": ["penalize"], "9.2 4.8 4.5": ["accelerates"], "5.6 0.3 3.4": ["peripherals"], "0.2 -3.0 2.1": ["hostel"], "12.7 15.4 9.5": ["handily"], "20.1 6.2 6.3": ["cradle"], "3.3 3.4 2.7": ["centrifuges"], "7.0 18.5 9.9": ["multiply", "unprogressive"], "4.6 22.2 4.1": ["destabilizing"], "3.5 11.8 4.9": ["cellar"], "14.6 13.0 8.5": ["bloke"], "3.0 5.6 0.9": ["governs"], "3.9 3.4 1.8": ["solidified"], "1.9 10.3 8.4": ["excessively"], "12.4 13.9 8.8": ["descending"], "10.9 12.5 3.9": ["galaxies"], "5.7 16.1 4.5": ["manifest"], "3.8 10.3 2.3": ["effortlessly"], "3.1 6.6 5.6": ["horizons"], "10.2 7.3 3.4": ["impressively"], "-0.9 2.9 2.5": ["infractions"], "6.7 4.0 10.5": ["sparse"], "7.0 12.3 -2.5": ["conduit"], "1.0 3.7 11.7": ["wealthier"], "19.6 9.5 2.5": ["nationalized"], "5.2 1.6 9.2": ["bouquet"], "-5.8 5.9 10.4": ["unmarried"], "8.1 3.7 8.2": ["nun"], "6.5 5.3 12.0": ["residue"], "-0.0 7.5 0.3": ["classify"], "4.2 8.3 7.9": ["enzymes"], "1.9 -3.6 2.9": ["postponing"], "-1.9 8.4 -0.6": ["scoreline"], "2.2 6.6 3.2": ["blighted"], "-0.9 -2.2 3.0": ["clocking"], "-6.7 9.2 7.4": ["civility"], "20.8 3.9 2.0": ["nestled"], "-0.3 3.8 5.0": ["forfeited"], "2.1 7.1 10.8": ["loft"], "2.5 5.6 -1.9": ["filtration"], "-10.3 -0.3 11.8": ["bullion"], "3.6 18.7 6.5": ["harass"], "5.2 8.8 9.7": ["apprentice"], "5.5 14.4 5.3": ["fullest"], "-3.7 9.8 8.3": ["wiser"], "-5.3 3.6 21.9": ["breeders"], "2.2 -3.5 0.8": ["uptake"], "5.0 5.5 7.8": ["notching"], "-2.1 6.2 19.3": ["charters"], "-7.0 5.1 -0.1": ["ppg"], "11.0 6.0 22.8": ["plywood"], "-2.1 2.2 7.1": ["cohort"], "16.2 8.3 5.2": ["mocking"], "-0.6 0.8 4.0": ["diplomas"], "-3.1 4.1 1.1": ["reprimanded"], "1.7 11.6 2.5": ["believable"], "3.9 2.2 6.7": ["crowding"], "8.2 8.1 8.3": ["trot"], "9.6 18.5 -1.3": ["uniting"], "-0.9 5.4 3.0": ["assays"], "1.3 3.3 1.0": ["esteemed"], "12.8 6.8 4.7": ["crank"], "6.4 14.1 2.9": ["disgraceful"], "5.8 10.9 8.8": ["scattering"], "1.1 -1.3 10.3": ["milligrams"], "8.5 10.1 25.1": ["paddle"], "15.0 6.9 -1.2": ["reinvent"], "13.2 5.1 2.8": ["rebirth"], "-8.3 5.9 23.3": ["snowmobile"], "-0.0 11.3 7.4": ["dependents"], "2.1 7.7 5.3": ["experimentation"], "7.0 12.7 -1.0": ["thunderstorm"], "10.6 7.3 6.4": ["rightful"], "5.1 9.5 24.3": ["hogs"], "-2.0 7.8 5.2": ["handers"], "-1.0 0.2 2.9": ["evaluates"], "-0.8 1.2 -3.5": ["relinquished"], "-4.4 11.6 8.3": ["heterosexual"], "8.4 15.1 20.2": ["jerk"], "25.7 18.2 6.4": ["swarm"], "-0.2 13.1 2.6": ["minimized"], "23.6 15.2 32.9": ["frogs"], "11.8 4.6 13.7": ["coloring"], "8.7 -9.7 2.3": ["gamut"], "1.2 1.0 -6.3": ["mediate"], "7.9 5.8 4.5": ["stash"], "-3.7 2.4 0.2": ["verifying"], "12.0 13.5 8.6": ["rubbing"], "9.6 28.9 12.3": ["bullies"], "9.7 3.4 3.3": ["preferential"], "21.6 9.1 7.4": ["symbolize"], "17.7 12.8 2.5": ["invent"], "-1.7 8.0 5.0": ["appointee", "serovar"], "1.8 14.9 6.7": ["itching"], "-6.6 30.5 12.4": ["munitions"], "6.2 8.9 6.0": ["modifying"], "-0.9 6.5 1.6": ["bestowed"], "-3.8 -4.9 -3.6": ["quizzed"], "3.6 11.1 11.6": ["deforestation"], "4.4 4.3 1.3": ["reviewers"], "3.1 8.2 9.0": ["stripe"], "9.6 12.6 -3.1": ["shielded"], "7.2 1.5 6.2": ["evaporated"], "8.8 8.0 4.0": ["gauges"], "-1.3 7.9 0.7": ["embodied"], "14.1 8.9 14.0": ["graceful"], "-1.4 15.0 6.6": ["contraband"], "1.4 -1.5 8.1": ["legalization"], "2.1 6.6 5.7": ["pathology"], "0.1 -3.8 1.7": ["deliberating"], "9.3 3.9 4.8": ["resurrected"], "-0.8 1.8 -0.3": ["orthopedic"], "-1.2 6.3 2.2": ["configure"], "-2.0 3.9 -1.1": ["editorials"], "19.8 2.2 -2.6": ["advert"], "-1.9 11.5 6.1": ["nonconference"], "5.3 4.0 8.1": ["shuffled"], "0.6 -2.1 4.2": ["rescind"], "20.9 9.6 1.4": ["reshape"], "5.9 10.3 24.2": ["oranges"], "-0.6 12.7 1.1": ["tragically"], "-5.8 9.9 9.1": ["unitholders"], "16.1 -0.3 7.8": ["directories"], "7.8 7.0 1.8": ["jubilant"], "-3.1 19.9 3.7": ["assassinations"], "6.7 19.7 3.5": ["paranoia"], "-5.5 12.0 6.3": ["reformist"], "2.3 10.9 13.5": ["kerosene"], "15.0 0.7 -4.7": ["philanthropist"], "8.3 5.3 -3.6": ["tireless"], "8.1 16.3 4.5": ["inhabited"], "-3.7 10.3 15.5": ["vineyards"], "3.9 4.3 13.0": ["treble"], "3.9 28.5 7.1": ["oppressive"], "7.1 11.7 4.3": ["inducing"], "8.2 14.0 6.9": ["adaptive"], "12.6 10.9 2.0": ["infringing"], "11.7 17.0 14.1": ["clone"], "3.8 7.6 0.9": ["sneaked"], "18.3 11.5 4.5": ["darkened"], "8.0 8.9 8.2": ["patchwork"], "21.9 16.0 15.8": ["puppets"], "15.6 9.9 6.8": ["dashing"], "4.3 10.5 0.6": ["neutrality"], "2.9 -0.2 4.8": ["disallowed"], "7.2 18.9 6.1": ["tenacious"], "8.1 5.4 10.8": ["weave"], "7.1 8.6 31.2": ["chicks"], "2.5 3.9 2.3": ["dignified"], "-1.4 9.3 0.8": ["assessor"], "3.0 15.5 9.9": ["presume"], "8.6 3.2 5.8": ["tripping"], "4.7 5.7 28.5": ["ferries"], "4.5 6.0 26.4": ["rods"], "6.0 17.2 11.2": ["inept"], "2.0 14.0 15.6": ["creeks"], "0.8 10.2 0.4": ["repealing"], "8.0 11.5 17.2": ["craving"], "1.9 20.3 1.9": ["overt"], "9.1 5.3 -2.3": ["showered"], "34.2 20.5 10.1": ["monstrous"], "11.9 4.5 3.9": ["shun"], "3.3 3.4 -5.4": ["hailing"], "2.0 0.9 1.4": ["upkeep"], "11.8 6.6 9.4": ["allure"], "1.4 -1.9 5.9": ["boutiques"], "13.5 1.5 2.3": ["styled"], "10.6 13.0 7.1": ["industrialized"], "1.0 7.1 -3.6": ["sermons"], "5.2 -6.5 4.4": ["sported"], "7.9 22.4 2.3": ["penetrating"], "2.8 11.3 3.6": ["preoccupied"], "11.2 11.7 20.0": ["whack"], "-2.2 0.4 8.0": ["chalked"], "20.4 18.1 0.9": ["toppling"], "4.2 17.2 11.3": ["longing"], "11.1 9.8 6.2": ["hysteria"], "-0.6 5.5 -0.8": ["rpm"], "3.1 4.7 4.4": ["woodwork"], "4.5 9.4 15.8": ["stale"], "-6.0 3.8 6.9": ["captained"], "10.7 7.4 7.0": ["stakeholder"], "0.1 4.7 13.2": ["anemia"], "10.6 -7.2 12.5": ["daylong"], "-3.4 19.3 4.9": ["waterboarding"], "14.6 -2.4 1.9": ["heady"], "8.6 17.8 0.8": ["dispatching"], "2.2 19.8 5.6": ["bleed"], "3.7 6.4 12.8": ["primetime"], "5.6 11.1 2.6": ["orphan"], "6.6 9.8 24.3": ["hunts"], "14.1 11.8 3.6": ["beheaded"], "0.6 12.8 1.2": ["imam"], "4.7 14.5 5.6": ["reckoning"], "-2.9 7.7 7.3": ["vested"], "11.4 8.1 9.7": ["mug"], "-1.1 2.7 1.8": ["petitioners"], "4.4 -1.5 -1.1": ["shopped"], "-5.8 15.7 -2.1": ["complication"], "1.1 -0.5 0.9": ["cardiologist"], "7.0 11.5 9.9": ["exclaimed"], "0.8 4.2 17.0": ["yarn"], "4.2 5.9 4.5": ["nab"], "-9.7 14.6 1.9": ["hawkish"], "13.1 14.8 2.4": ["stinging"], "2.5 8.0 1.8": ["heartbreak"], "9.0 18.3 9.3": ["softly"], "12.3 3.7 -2.9": ["prototypes"], "28.8 33.4 14.6": ["zombies"], "12.3 6.6 2.7": ["throng"], "-3.2 19.0 11.5": ["eradication"], "12.9 1.2 7.0": ["furor"], "4.8 10.3 18.6": ["dives", "laminae"], "7.3 13.1 9.9": ["messing"], "-6.5 21.4 7.2": ["reservists"], "12.1 25.0 8.8": ["avatar"], "8.1 9.2 5.0": ["glimpses"], "12.2 8.6 2.9": ["litany"], "4.3 8.1 4.8": ["mop"], "-1.2 6.3 -3.3": ["frequented"], "-2.6 7.7 13.5": ["brides"], "5.7 4.9 5.5": ["commotion"], "-6.9 11.5 0.3": ["verses"], "-0.3 11.3 8.2": ["basing"], "7.5 15.4 2.6": ["smartest"], "10.4 3.4 15.9": ["scrape"], "13.5 12.4 11.9": ["lore"], "8.1 14.2 4.8": ["infect"], "4.5 1.8 -1.9": ["mediators"], "-1.4 6.0 3.1": ["secluded"], "7.8 2.3 5.1": ["foothills"], "-3.5 8.3 5.7": ["clemency"], "4.4 8.7 11.1": ["alternating"], "13.0 5.1 1.2": ["privatized"], "3.2 7.4 4.3": ["similarity"], "21.4 -0.1 1.7": ["rocketed"], "2.5 1.6 0.8": ["testifies"], "5.1 7.3 5.5": ["unexplained"], "16.3 2.8 10.2": ["nudge"], "0.2 8.6 5.2": ["arduous"], "17.0 8.8 12.0": ["brokerages"], "14.7 3.2 7.0": ["oilfield"], "5.2 -0.6 0.5": ["complies"], "7.3 8.0 1.8": ["evoke", "bestirred"], "12.3 21.2 25.7": ["fungus"], "17.9 6.1 3.4": ["nationalization"], "9.2 17.3 1.1": ["penetrated"], "10.8 12.4 -1.8": ["emanating"], "2.9 3.8 0.9": ["remodeled"], "21.4 18.1 26.6": ["minnows"], "12.1 22.8 6.2": ["cyberspace"], "2.4 -1.9 5.1": ["interns"], "-0.7 7.9 7.0": ["nightcap"], "9.8 5.1 4.5": ["flyer"], "5.9 17.2 19.7": ["flotilla"], "1.9 3.2 9.8": ["trending"], "6.9 11.7 10.9": ["textures"], "12.4 0.4 -1.9": ["seminal"], "-2.4 16.4 5.2": ["permissible"], "11.8 5.2 5.8": ["buckled"], "-1.1 5.8 6.4": ["renewables"], "17.6 5.8 8.4": ["tilted"], "2.8 10.1 7.2": ["hysterical", "benzema"], "6.2 8.3 5.4": ["discrete"], "1.7 -1.4 4.7": ["standouts"], "1.0 4.0 -2.8": ["fostered"], "-1.0 12.2 8.9": ["ballad"], "-3.2 7.7 2.2": ["voicemail"], "6.7 14.6 2.4": ["rebuke"], "3.3 4.6 10.0": ["ratepayers"], "1.9 22.0 10.1": ["servants"], "10.2 14.2 1.3": ["plains"], "3.3 16.2 -1.8": ["transmitting"], "19.9 12.7 7.9": ["vaunted"], "1.7 7.3 5.8": ["rationing"], "5.5 9.8 9.1": ["righty"], "14.9 21.6 10.6": ["infested"], "-8.0 2.6 4.1": ["remission"], "-9.2 10.0 -1.1": ["reprimand"], "3.9 15.6 5.5": ["frustrate"], "9.1 1.0 6.5": ["strung"], "11.0 5.7 -2.0": ["illustrious"], "0.0 4.7 2.2": ["deficient"], "-3.9 16.2 1.9": ["underrated"], "3.4 3.0 3.4": ["stipulates"], "4.7 12.7 8.7": ["nonexistent"], "3.4 5.5 12.6": ["keyword"], "13.8 10.9 8.4": ["barren"], "-1.6 0.2 3.3": ["lenient"], "-2.6 8.5 7.6": ["exacerbate"], "16.6 -1.5 2.7": ["raked"], "5.0 5.8 4.3": ["snub"], "7.7 -0.9 1.8": ["biomedical"], "2.4 6.8 27.7": ["roasted"], "3.6 -1.8 9.0": ["roofing"], "3.5 6.3 7.0": ["millimeters"], "1.1 10.9 4.2": ["incurring"], "1.9 12.3 7.1": ["throats"], "-7.2 9.8 3.3": ["theological"], "9.9 13.5 6.7": ["shutter"], "-0.6 2.7 5.0": ["routers"], "18.1 2.7 -2.3": ["momentous"], "8.1 -1.9 5.5": ["bi"], "9.5 5.6 3.5": ["redundancies"], "4.5 9.6 8.1": ["wrinkles"], "5.8 3.6 -0.6": ["hp"], "8.1 5.7 18.8": ["chops"], "-6.1 9.6 4.4": ["viewpoints"], "14.1 12.5 2.9": ["sniff"], "9.6 1.6 -2.8": ["corporates"], "5.5 9.6 5.9": ["astronomy"], "8.0 4.8 1.9": ["downplay"], "-3.9 4.0 -2.0": ["accorded"], "4.9 10.9 21.4": ["diver"], "14.0 -0.4 3.1": ["subsidizing"], "10.9 13.3 11.5": ["bedrock"], "7.2 3.3 6.6": ["fairer"], "8.7 7.6 2.8": ["impractical"], "15.6 -0.2 11.9": ["tiered"], "-4.9 3.5 5.2": ["conflicted"], "8.3 21.3 6.3": ["perilous"], "12.5 14.2 10.6": ["darn"], "-3.0 0.4 8.9": ["quilts"], "5.0 6.7 2.9": ["workings"], "6.3 18.9 6.7": ["tantamount"], "4.3 10.1 7.3": ["equaling"], "5.6 3.0 9.8": ["sweeter"], "3.7 4.1 10.0": ["payday"], "-11.9 5.9 12.8": ["breaststroke"], "3.0 0.9 4.4": ["competitively"], "13.3 6.8 3.8": ["doused"], "6.0 1.2 8.7": ["housewife"], "-6.8 21.2 2.9": ["coercion"], "3.6 -2.9 4.1": ["waned"], "4.3 11.7 8.8": ["motorcyclist"], "7.2 6.2 2.4": ["tract"], "4.7 0.8 3.4": ["underprivileged"], "8.8 7.9 7.3": ["masterful"], "9.1 20.5 -1.8": ["darkest"], "10.9 21.4 9.0": ["jamming"], "4.1 15.2 3.2": ["hypocritical"], "2.5 10.0 14.9": ["anime"], "6.4 0.6 6.6": ["postage"], "6.6 15.5 2.7": ["zeal"], "7.3 1.3 -3.1": ["ombudsman"], "0.8 1.7 -3.1": ["synthesis"], "3.8 12.4 5.6": ["flirting"], "-3.3 2.4 23.1": ["nutrient"], "4.9 30.0 3.3": ["neutralize"], "2.9 9.5 2.0": ["deplorable"], "-6.1 2.4 6.0": ["carers"], "9.9 7.3 4.8": ["patched"], "2.0 9.8 21.0": ["grower"], "18.1 26.0 -0.7": ["shadowy"], "-5.7 32.0 3.4": ["airmen"], "7.6 6.9 6.7": ["pic"], "4.7 6.8 0.9": ["reviewer"], "10.2 -2.9 1.8": ["phasing"], "6.0 -5.9 18.2": ["melamine"], "4.6 6.9 3.7": ["crib"], "29.2 -2.0 9.3": ["bonanza"], "5.9 16.2 -0.0": ["terrorized"], "-0.1 12.4 6.3": ["sane"], "-0.7 6.9 10.3": ["poetic"], "-2.0 11.2 15.0": ["liftoff"], "13.9 7.6 3.1": ["synchronized"], "-8.0 20.0 1.8": ["cohesion"], "10.7 9.4 5.2": ["resurrection"], "6.8 6.4 9.0": ["celebs"], "8.2 20.1 11.7": ["adage"], "0.5 12.6 0.9": ["whispered"], "-5.2 19.0 -4.8": ["selfless"], "0.7 8.8 9.3": ["funniest"], "12.9 11.9 1.9": ["laughable"], "3.3 4.2 3.9": ["randomized"], "8.7 6.5 1.9": ["courier"], "-3.6 11.2 13.6": ["locality"], "12.6 -0.9 18.2": ["pans"], "3.4 10.2 2.5": ["unregistered"], "5.2 3.6 4.2": ["pajamas"], "1.7 0.6 1.6": ["spec"], "6.6 23.6 4.9": ["whisper"], "8.1 -1.4 1.3": ["blossomed"], "5.2 16.2 7.4": ["teasing"], "0.0 7.3 -5.1": ["piloted"], "2.0 5.0 5.4": ["interfered"], "5.1 4.4 0.6": ["headcount"], "15.2 19.6 16.0": ["hawk"], "10.9 -1.1 5.2": ["dept"], "10.2 -0.4 1.8": ["languishing"], "2.6 7.9 4.1": ["reconstruct"], "2.7 4.5 3.6": ["synchronization"], "16.9 13.4 6.1": ["graveyard"], "2.6 14.6 23.8": ["subs"], "4.6 13.9 7.0": ["cant"], "0.5 27.2 3.3": ["martyrs"], "-0.7 19.1 3.6": ["intellect"], "10.5 8.5 1.0": ["refocus"], "10.5 6.2 4.1": ["entrant"], "1.7 -4.8 -2.3": ["questionnaires"], "13.6 6.2 4.4": ["derided"], "7.7 3.5 14.3": ["tub"], "1.3 4.9 -2.0": ["gyms"], "13.5 5.5 6.9": ["uh"], "0.0 9.8 3.6": ["dialed"], "6.3 8.1 -1.4": ["simulations"], "9.8 6.1 6.5": ["elevators"], "4.2 12.8 7.5": ["grandchild"], "7.6 9.7 4.1": ["sleeps"], "-6.3 8.7 5.0": ["lyrical"], "13.1 2.8 5.2": ["refrigerators"], "7.4 3.3 6.1": ["hump"], "-7.3 0.0 7.5": ["airfare"], "0.1 7.6 10.2": ["statehood"], "13.9 24.8 4.6": ["cartels"], "-1.1 3.7 2.5": ["jeopardized"], "9.6 8.6 4.6": ["digit"], "6.3 5.1 1.8": ["unwind"], "3.1 2.6 7.1": ["plaques"], "-0.6 6.0 9.1": ["caveat"], "4.2 3.4 8.8": ["accompanies"], "6.4 10.3 3.4": ["tread"], "14.4 0.9 9.8": ["clawed"], "12.4 20.5 4.9": ["doorway"], "-3.5 9.0 15.9": ["vineyard"], "4.3 0.6 -4.6": ["courted"], "23.1 4.8 12.1": ["diminutive"], "3.5 2.4 -0.5": ["simplifies"], "7.6 4.8 2.2": ["lewd"], "14.4 24.0 31.1": ["fox"], "0.8 11.3 -1.3": ["successors"], "5.9 4.7 12.1": ["ecstasy"], "14.4 28.5 12.2": ["camouflage"], "-4.3 10.7 1.6": ["ignition"], "7.6 10.8 5.0": ["uprooted"], "-0.6 8.4 7.9": ["mutation"], "-4.0 3.3 14.2": ["chipset"], "6.5 8.4 7.6": ["redirect"], "-5.3 34.8 9.5": ["squadron"], "10.6 23.5 9.3": ["outposts"], "13.2 -1.1 9.6": ["toothpaste"], "10.5 -0.2 5.7": ["mandating"], "-6.3 4.7 11.8": ["fluctuate"], "-0.0 6.8 7.3": ["architectures"], "-3.2 11.3 5.1": ["humid"], "-5.4 12.1 0.0": ["therapeutics"], "12.9 6.3 1.2": ["forbids"], "14.7 17.9 6.6": ["cornered"], "-2.0 3.1 10.3": ["hydroelectric"], "8.9 6.2 3.4": ["signifies"], "13.6 19.0 7.8": ["eternity"], "5.3 4.2 7.3": ["middleware"], "-0.5 2.8 13.6": ["snowboarding"], "14.2 3.5 14.5": ["soggy"], "-2.7 2.9 -1.0": ["diaries"], "3.5 17.7 1.9": ["abusers"], "2.1 4.4 3.2": ["originality"], "15.2 2.6 13.8": ["plugs"], "4.7 11.5 27.9": ["nesting"], "12.5 8.8 7.7": ["matrix"], "8.5 10.4 8.8": ["parting"], "5.9 16.5 10.5": ["whining"], "25.1 -3.8 11.1": ["biz"], "13.9 5.2 10.1": ["merry"], "10.6 4.8 -2.7": ["scouring"], "1.8 3.3 -0.2": ["preclude"], "9.1 7.0 -1.8": ["transports"], "9.9 18.6 9.5": ["bulldozers"], "11.6 3.5 6.1": ["glimmer"], "11.7 4.3 3.9": ["overturning"], "12.2 10.9 11.5": ["fuse"], "-2.6 14.5 8.3": ["adultery"], "8.6 6.8 14.3": ["chimney"], "6.3 24.9 -2.1": ["lawless"], "0.2 8.6 8.7": ["depositors"], "-4.1 2.6 2.4": ["therapists"], "-0.6 0.7 15.0": ["artisans"], "-0.9 10.8 4.0": ["memorials"], "-3.2 3.5 22.1": ["nutritious"], "6.7 3.6 6.3": ["watt"], "9.8 42.3 9.5": ["snipers"], "-3.8 24.3 7.2": ["cadres"], "12.1 12.6 17.4": ["phishing"], "7.2 6.9 9.4": ["bookmakers"], "-5.6 5.3 3.5": ["nd"], "7.4 11.5 9.0": ["joys"], "-4.2 -1.9 -7.0": ["validates"], "2.5 5.3 6.0": ["acumen"], "10.0 2.9 6.0": ["incubator"], "-12.2 7.6 10.9": ["prose"], "8.5 10.4 12.1": ["terrace"], "2.1 4.2 -1.3": ["reaffirm"], "1.8 10.7 16.1": ["communion"], "13.1 16.3 5.3": ["incidentally"], "-8.1 14.9 0.2": ["motivates"], "5.2 7.8 2.7": ["untested"], "7.2 6.1 6.4": ["tinkering"], "7.5 8.5 5.2": ["diversifying"], "2.1 15.7 14.6": ["curveball"], "9.1 13.6 13.5": ["amusement"], "5.0 -5.5 -5.1": ["shortlisted"], "19.9 12.9 -1.7": ["lobbies"], "4.8 12.7 0.2": ["irritation"], "9.0 2.9 0.5": ["typed"], "-10.6 15.6 -0.5": ["actionable"], "10.5 0.2 15.1": ["lb"], "15.2 14.8 3.9": ["eerie"], "12.9 7.9 21.4": ["crackers"], "4.4 13.1 3.5": ["intermittent"], "6.4 14.9 7.6": ["chases"], "15.7 8.3 18.0": ["cheesy"], "0.1 12.7 1.3": ["contradictions"], "10.2 3.2 7.1": ["tv", "celebra"], "5.4 4.3 0.8": ["labored"], "4.7 5.5 25.6": ["crust"], "13.2 10.6 3.6": ["blogosphere"], "-5.2 5.8 7.1": ["pars"], "-0.2 -2.2 -6.0": ["vetting"], "6.1 13.9 5.4": ["allergic"], "3.8 14.5 3.2": ["degrading"], "9.5 11.4 -1.0": ["insurmountable"], "9.5 12.4 -3.5": ["modernizing"], "4.7 0.1 7.7": ["wholesome"], "-6.4 -0.5 -0.5": ["accommodated"], "12.1 12.0 5.0": ["extracting"], "1.6 -3.0 7.2": ["limousine"], "12.2 5.0 4.7": ["privatize"], "10.5 8.3 3.0": ["electrician"], "22.0 3.9 6.2": ["lighted"], "6.0 16.0 8.2": ["propensity"], "10.5 12.4 10.6": ["symbolism"], "4.0 21.2 10.8": ["plainly"], "13.9 17.1 4.2": ["unwittingly"], "0.4 14.9 4.6": ["harms"], "-2.8 -1.8 13.7": ["bracelets"], "4.3 6.3 6.5": ["joyful"], "24.2 5.1 6.7": ["propped"], "14.1 7.3 6.6": ["footprints"], "13.2 5.2 6.4": ["resurrect"], "13.9 22.7 8.4": ["untold"], "3.0 7.9 8.9": ["scientifically"], "-0.8 12.0 11.1": ["footwork"], "9.9 2.2 1.8": ["strolled"], "-2.9 30.7 -2.1": ["heroism"], "-7.7 -2.6 5.4": ["redshirt"], "4.0 18.7 11.7": ["numb"], "13.0 4.2 17.6": ["feather"], "14.5 7.6 10.1": ["capitol"], "-6.4 7.3 6.2": ["regionally"], "18.5 0.9 4.6": ["spoof"], "-0.3 14.9 6.0": ["harshly"], "2.5 11.7 2.0": ["aspiration"], "5.6 10.0 15.3": ["camper"], "7.7 12.6 2.6": ["hobbies"], "5.2 7.7 7.7": ["suffice"], "5.2 16.6 9.7": ["barking"], "8.0 0.2 10.2": ["fret"], "-1.6 -1.2 -1.1": ["sporty"], "3.3 10.1 3.8": ["prerequisite"], "5.5 14.4 1.4": ["spoiler"], "5.6 5.9 1.1": ["inappropriately"], "16.6 16.8 6.0": ["legions"], "0.9 21.1 2.1": ["repressive"], "5.6 15.7 2.0": ["backfire"], "5.6 13.4 5.9": ["wont"], "5.7 17.3 5.3": ["manning"], "4.6 2.2 21.9": ["deli"], "12.7 15.2 7.3": ["wield"], "18.3 49.6 15.0": ["invaders"], "-4.3 1.2 6.6": ["anecdotes"], "10.7 -2.0 13.9": ["bottomed"], "2.3 -5.6 -2.8": ["resell"], "16.6 6.4 -1.8": ["tricked"], "-5.4 12.2 7.1": ["philosophies"], "-8.6 15.5 2.2": ["confrontational"], "12.8 16.8 11.6": ["inexplicably"], "-2.3 8.5 9.2": ["forfeiture"], "11.9 1.8 10.0": ["giddy"], "10.1 6.6 13.6": ["gag"], "4.7 6.7 4.4": ["astonished"], "5.3 -1.0 8.7": ["sprinkled"], "26.8 31.7 25.7": ["ants"], "6.9 9.5 20.0": ["glaciers"], "7.4 14.6 9.8": ["timid"], "23.2 7.2 12.1": ["telco"], "-0.5 3.9 4.3": ["molestation"], "0.6 4.1 20.2": ["pantry"], "4.9 15.9 2.9": ["overpowered"], "18.8 4.5 -6.7": ["divest"], "9.5 6.3 10.5": ["malaise"], "-9.5 22.7 1.1": ["subordinate"], "5.2 17.7 6.6": ["persistently"], "1.5 15.8 2.1": ["infidelity"], "13.1 35.1 3.2": ["mercenaries"], "11.9 -0.8 10.0": ["drumming"], "3.2 6.7 6.9": ["deduct"], "3.8 17.7 4.3": ["negativity"], "-2.6 2.7 0.2": ["narrated"], "7.4 14.4 -5.8": ["spokesmen"], "-2.9 14.7 32.0": ["angler"], "9.5 0.7 14.4": ["jockeys"], "1.9 11.8 14.4": ["wager"], "2.9 8.7 2.2": ["blackouts"], "10.2 3.7 3.8": ["glanced"], "6.2 13.2 -0.5": ["implicit"], "-2.9 1.4 3.1": ["cleanliness"], "13.2 6.6 2.2": ["orchestrating"], "1.4 11.8 8.5": ["pursuits"], "-4.7 3.3 5.0": ["breastfeeding"], "13.6 7.0 9.6": ["graphical"], "16.5 17.4 11.9": ["fucking"], "17.4 10.5 6.3": ["suitors"], "8.2 8.5 10.1": ["markings"], "21.8 2.7 5.8": ["soars"], "8.3 1.7 10.1": ["washes"], "11.2 2.3 11.1": ["summits"], "-0.8 -1.4 2.1": ["gloss"], "-12.5 8.6 10.7": ["superdelegates"], "-2.4 2.5 6.5": ["replication"], "5.6 23.1 6.8": ["compatriots"], "-0.2 3.8 -2.8": ["enriching"], "7.3 7.9 29.8": ["gravy"], "10.0 1.6 9.1": ["scraped"], "3.4 24.0 0.4": ["airfield"], "9.7 1.3 6.1": ["outlooks"], "6.9 3.5 27.9": ["creamy"], "1.3 -6.7 -1.2": ["cropped"], "-1.5 1.5 12.1": ["menopause"], "6.6 8.5 13.8": ["bouncer"], "2.4 7.5 1.8": ["reconnect"], "3.9 6.9 13.2": ["uptrend"], "5.4 -1.0 -6.9": ["warranties"], "9.8 8.7 8.0": ["naughty"], "3.3 11.6 3.7": ["exponentially"], "7.5 19.8 8.4": ["futility"], "2.8 -0.9 -1.0": ["snubbed"], "3.0 18.3 13.6": ["felon"], "10.5 12.0 3.6": ["inward"], "15.2 7.4 3.2": ["maligned"], "10.9 1.3 0.8": ["underline"], "10.4 6.6 16.6": ["dye"], "6.2 0.7 2.7": ["funneled"], "5.1 9.5 28.7": ["salty"], "5.3 12.3 8.3": ["byproduct"], "-1.0 -3.5 0.4": ["affidavits"], "7.2 5.9 10.0": ["virgin"], "4.8 9.1 -0.8": ["collusion"], "-2.1 5.1 -3.2": ["responsiveness"], "2.3 10.4 13.2": ["middleweight"], "-2.5 5.2 1.5": ["additionally"], "2.1 12.0 0.6": ["ousting"], "15.9 -0.4 5.8": ["luminaries"], "-10.1 3.5 3.2": ["opined"], "-6.2 5.8 1.9": ["unqualified"], "-2.7 17.9 10.0": ["evangelicals"], "14.2 8.4 10.9": ["likeness"], "5.9 9.9 -1.3": ["overtures"], "10.8 -2.8 13.6": ["monthlong"], "13.0 15.3 3.2": ["concealing"], "5.0 12.1 2.4": ["backline"], "-3.0 19.6 6.2": ["ambiguity"], "10.5 21.8 8.8": ["flashlight"], "-2.6 6.7 4.8": ["dosage"], "4.3 2.5 21.6": ["eateries"], "1.7 3.4 -2.3": ["reiterating"], "4.1 1.6 10.4": ["tiers"], "11.4 2.8 7.5": ["casing"], "0.7 9.2 9.7": ["quakes"], "6.8 3.7 19.5": ["barges"], "13.0 10.1 32.0": ["pumpkins"], "5.3 24.2 6.8": ["supernatural"], "8.4 11.5 8.1": ["angled"], "-4.5 7.1 5.6": ["mingle"], "-4.2 14.9 5.0": ["respectfully"], "8.2 3.1 -2.4": ["debuting"], "2.7 20.9 1.5": ["retaliated"], "13.7 11.7 7.1": ["scorched"], "1.1 9.9 -0.1": ["intermediaries"], "6.6 10.3 47.5": ["coral"], "2.8 3.2 0.3": ["accolade"], "-5.5 11.1 12.2": ["dwellings"], "8.9 17.2 9.7": ["fantasies"], "8.1 18.1 4.7": ["atoms"], "11.2 5.9 5.2": ["derives"], "18.8 4.4 14.4": ["whimsical"], "-6.4 11.7 14.4": ["soils"], "1.6 8.9 19.7": ["tavern"], "-3.8 8.7 4.0": ["assigning"], "18.9 27.3 8.6": ["infinite"], "6.7 14.9 8.4": ["posturing"], "1.6 -0.9 -2.7": ["marketable"], "8.6 10.2 2.0": ["dodged"], "-9.1 8.9 14.4": ["contraception"], "7.3 6.7 9.3": ["collectibles", "despond"], "14.6 5.4 6.9": ["magnets"], "7.0 10.2 7.8": ["caption"], "7.5 8.5 1.6": ["mobiles"], "10.0 23.4 12.4": ["fools"], "13.0 10.8 3.9": ["addict"], "-0.3 4.3 11.5": ["immersion"], "9.7 31.1 21.6": ["warship"], "9.4 13.2 5.7": ["visualize"], "14.0 14.5 4.3": ["literal"], "7.7 0.6 5.0": ["fourths"], "6.4 11.5 6.1": ["seekers"], "-3.2 4.6 7.4": ["furlong"], "5.2 -2.0 3.1": ["steeped"], "1.4 -0.5 -0.9": ["enthused"], "-0.8 11.0 6.9": ["heartbroken"], "-4.1 12.6 3.1": ["preventative"], "0.5 5.3 8.9": ["excursion"], "4.6 6.0 3.0": ["twitter"], "4.4 3.8 2.5": ["fringes"], "-1.0 9.8 -4.1": ["abductions"], "-1.0 8.2 30.9": ["kayak"], "8.0 8.3 6.7": ["overload"], "10.1 12.2 -0.6": ["aligning"], "5.2 3.4 1.3": ["spurned"], "14.1 9.7 4.5": ["colliding"], "5.9 16.1 5.2": ["weeping"], "11.5 19.0 5.8": ["unison"], "3.6 7.3 -2.9": ["ransacked"], "18.6 -0.8 4.1": ["vaulted"], "2.6 5.0 -2.3": ["refreshed"], "13.6 9.6 48.3": ["dolphin"], "2.3 8.8 14.6": ["cheeks"], "10.2 14.5 4.9": ["ills"], "-0.3 6.1 3.5": ["correspond"], "13.1 9.4 28.4": ["hamburger"], "3.6 19.1 3.0": ["brigades"], "15.1 11.2 14.3": ["climber"], "10.8 10.8 12.2": ["comical"], "-4.3 7.5 13.8": ["archaeological"], "1.2 -0.6 20.0": ["wig"], "5.1 5.9 5.9": ["flier"], "3.0 2.2 -0.8": ["chronicled"], "11.3 8.2 6.0": ["playgrounds"], "-2.0 -4.4 5.6": ["resurfacing"], "7.4 5.9 0.4": ["riveting"], "4.3 3.2 23.6": ["roast"], "4.8 13.0 3.3": ["transmitter"], "-4.0 1.4 1.0": ["exonerated"], "5.4 5.4 5.7": ["quarantined"], "1.1 9.0 5.4": ["bottlenecks", "indies"], "17.5 6.9 10.6": ["attaching"], "-2.4 6.1 11.8": ["rappers"], "14.6 5.9 9.8": ["tangle"], "12.6 16.4 13.4": ["momentarily"], "-1.9 9.8 -5.6": ["affirmation"], "0.4 7.6 6.2": ["monastery"], "12.2 19.6 1.1": ["countering"], "10.1 3.3 5.1": ["clouded"], "4.5 8.9 5.4": ["underwriter"], "-0.6 15.9 6.2": ["kisses"], "4.8 8.6 -3.2": ["profitably"], "5.7 6.8 4.4": ["riskier"], "1.6 2.1 11.0": ["deletion"], "3.6 -1.8 12.8": ["mainframe"], "1.9 10.3 36.9": ["whaling"], "13.3 11.6 28.9": ["buffalo"], "1.9 0.8 5.1": ["additives"], "0.9 2.6 -2.3": ["hallmarks"], "3.8 9.3 8.2": ["engraved"], "8.4 5.1 2.9": ["flicked"], "0.6 1.0 3.6": ["pooled"], "-10.1 1.3 1.3": ["biographies"], "12.3 17.6 8.9": ["hoses"], "13.6 -0.3 -0.5": ["captivated"], "14.9 16.0 7.5": ["endlessly"], "9.4 20.6 10.4": ["imperfect"], "10.2 15.0 7.1": ["sprinting"], "8.8 1.7 4.5": ["overloaded"], "16.7 14.2 12.2": ["clumsy"], "-2.4 9.5 14.3": ["beginner"], "5.7 9.5 6.1": ["staircase"], "11.1 3.7 10.0": ["patriarch"], "1.2 6.3 15.8": ["juices"], "-3.0 18.8 1.6": ["eyewitness"], "17.3 10.6 4.0": ["bailing"], "4.6 11.6 7.8": ["firemen"], "10.1 12.1 8.6": ["perfected"], "2.2 10.9 13.4": ["medley"], "-2.7 12.3 6.9": ["exceedingly"], "12.9 7.6 30.0": ["peanut"], "2.9 5.1 10.4": ["unsold"], "6.8 1.0 18.1": ["kittens"], "11.2 14.4 3.4": ["buff"], "16.2 16.0 10.7": ["grinning"], "2.4 0.1 -8.6": ["refuted"], "13.8 10.4 7.1": ["venturing"], "7.6 1.3 1.9": ["underwritten"], "16.2 13.4 21.5": ["pod"], "18.3 5.1 11.3": ["vaguely"], "-1.8 9.4 3.3": ["occurrences"], "-0.2 1.1 10.9": ["increments"], "11.0 1.6 2.4": ["dispense"], "3.3 7.2 -3.2": ["razed"], "2.4 17.8 23.0": ["archery"], "11.9 5.8 -0.1": ["physicist"], "4.6 2.4 8.3": ["flux"], "12.9 2.5 7.8": ["thicker"], "5.7 15.0 13.7": ["tease"], "17.7 6.1 28.3": ["slab"], "2.4 19.3 3.6": ["undesirable"], "12.0 10.5 12.2": ["bearded"], "7.4 21.6 12.6": ["gangsters"], "7.0 7.5 15.5": ["shippers", "hyperkeratotic"], "22.1 23.6 10.6": ["hordes"], "-2.2 3.3 9.7": ["payers"], "-1.1 0.8 6.2": ["fetal"], "16.8 28.6 -1.7": ["fanatics"], "2.9 20.7 3.8": ["resolute"], "0.8 4.1 2.8": ["catalysts"], "-2.5 6.5 13.6": ["unincorporated"], "2.5 8.5 3.8": ["motoring"], "-3.9 0.6 6.2": ["villas"], "2.3 6.6 19.8": ["discard"], "16.7 3.3 15.4": ["camel"], "8.2 15.5 18.9": ["bacterial"], "7.6 -3.3 -2.5": ["facelift"], "2.0 6.6 3.8": ["checklist", "capacitor"], "4.2 10.8 5.9": ["energize"], "-14.0 1.3 9.5": ["ridership"], "6.1 6.2 9.1": ["paddock"], "5.6 -5.1 2.9": ["pocketed"], "6.2 13.1 2.8": ["compartment"], "18.6 10.1 16.1": ["blackened"], "17.8 14.6 6.9": ["nimble"], "-7.5 3.1 5.0": ["originals"], "4.7 10.6 7.0": ["sip"], "7.6 15.0 5.0": ["succumb"], "-2.8 4.4 8.2": ["motherhood"], "11.5 8.5 10.8": ["um"], "2.0 11.7 16.1": ["gardener"], "-2.5 14.3 13.4": ["jealousy"], "9.9 2.0 0.6": ["attractiveness"], "2.2 4.8 5.0": ["fives"], "8.5 14.6 5.5": ["abysmal"], "2.3 2.8 17.9": ["wafer"], "7.8 0.7 21.8": ["jars"], "-6.6 10.6 9.2": ["revolver"], "5.4 -2.5 5.3": ["trickled"], "20.1 -6.5 4.7": ["quadruple"], "4.2 3.7 1.9": ["solves"], "17.2 20.6 9.7": ["brethren"], "-1.5 15.2 -0.5": ["inconvenient"], "9.0 -0.9 2.1": ["outpacing"], "0.5 1.1 7.1": ["breezy"], "12.3 15.8 3.5": ["legion"], "1.6 15.4 10.2": ["lawlessness"], "10.0 16.5 0.6": ["detonate"], "14.1 5.8 10.6": ["exorbitant"], "-4.2 0.9 17.3": ["cartilage"], "1.3 2.7 -1.5": ["pathologist"], "4.8 0.4 -2.7": ["fulfills"], "13.2 12.3 40.8": ["goose"], "4.2 9.2 9.2": ["crave"], "16.8 10.0 4.8": ["signify"], "41.2 12.8 9.3": ["juggernaut"], "19.4 15.3 10.0": ["spheres"], "-6.3 19.0 8.0": ["safeties"], "15.0 20.7 14.6": ["predatory"], "-5.4 7.7 5.7": ["consular"], "14.7 -0.2 4.5": ["reaped"], "-3.9 6.2 10.4": ["alteration"], "1.4 -0.4 3.6": ["securitization"], "-1.1 3.8 9.3": ["soulful"], "8.6 -0.6 18.4": ["fossils"], "10.3 28.0 6.1": ["dictators"], "1.8 25.3 5.5": ["oneself"], "-0.7 -2.9 6.2": ["handbags"], "2.2 13.9 -4.1": ["deceived"], "10.1 8.8 15.6": ["peel"], "8.0 7.4 8.2": ["counterfeiting"], "14.8 10.3 21.6": ["slicing"], "-0.6 9.0 11.7": ["sparring"], "9.1 -2.6 11.8": ["luster"], "12.5 7.2 7.3": ["steeper"], "7.9 8.1 10.7": ["unionized"], "-4.1 20.3 -2.0": ["persecuted"], "6.7 2.4 11.3": ["strands"], "7.2 10.5 19.6": ["earmark"], "3.3 -0.2 9.0": ["connectors"], "14.8 5.7 -0.6": ["sprang"], "3.5 7.9 13.8": ["ancestry"], "8.2 1.1 13.9": ["badminton"], "9.8 8.7 4.9": ["molded"], "11.2 13.0 11.0": ["behold"], "6.2 9.4 3.3": ["thats"], "4.6 4.0 10.4": ["archaeologists"], "12.8 16.6 9.9": ["videogame"], "7.3 2.9 2.5": ["stimulation"], "9.9 14.4 7.4": ["bless"], "17.8 13.9 0.0": ["interconnected"], "24.8 -1.2 2.9": ["plush"], "0.2 19.8 1.0": ["reprisals"], "-11.7 3.7 6.6": ["childbirth"], "13.9 10.1 11.8": ["stout"], "-1.2 8.5 30.9": ["appetizers"], "8.3 9.4 8.4": ["backfired"], "17.2 -6.0 7.6": ["multiyear"], "-5.1 0.8 -4.8": ["vetted"], "6.6 -2.5 3.4": ["postcards"], "5.2 18.2 15.5": ["illegals"], "16.3 26.7 2.8": ["shields"], "-2.1 14.4 9.3": ["contiguous"], "11.3 12.0 5.9": ["antiquated"], "-8.8 -0.1 3.1": ["webinar"], "18.7 3.7 2.4": ["firestorm"], "-3.2 3.7 6.4": ["apprehensive"], "14.5 18.7 6.3": ["bastion"], "5.4 6.2 13.2": ["rite"], "7.5 7.1 5.4": ["thrills"], "16.6 11.0 7.1": ["astronomical"], "10.9 10.2 18.1": ["sled"], "-0.6 -1.1 1.9": ["toxicology"], "-10.1 4.0 -1.7": ["scholarly"], "9.2 2.2 16.0": ["trays"], "16.3 5.9 6.9": ["metropolis"], "18.9 5.7 7.7": ["curved"], "15.5 1.1 7.2": ["morphed"], "-0.6 8.2 1.3": ["gleaned"], "2.8 17.2 -0.5": ["inciting"], "-4.8 10.3 1.3": ["censure"], "19.2 4.6 -0.2": ["emblazoned"], "5.8 18.8 5.7": ["harboring"], "10.8 0.9 -0.1": ["receptionist"], "-0.4 -0.2 8.9": ["knotted"], "5.6 4.1 8.9": ["souvenirs"], "12.0 16.0 5.2": ["cleverly"], "0.3 11.1 0.6": ["distressing"], "0.8 5.3 4.2": ["motorsports"], "6.9 5.6 2.2": ["trumps"], "2.4 21.8 15.7": ["bitch"], "9.1 10.4 24.9": ["lime"], "6.6 -3.7 6.1": ["reopens"], "-0.9 28.5 5.1": ["medic"], "3.0 8.5 8.2": ["jeopardizing"], "4.1 5.8 -1.6": ["relieving"], "4.7 4.8 7.7": ["bypassing"], "17.9 15.5 -3.6": ["downing"], "13.9 3.3 0.5": ["hotbed"], "-5.0 12.1 7.5": ["mitigating"], "8.0 6.6 -0.4": ["withdraws"], "2.2 -3.1 3.3": ["balk"], "4.1 12.8 9.4": ["unorthodox"], "4.4 7.7 9.1": ["undersecretary"], "3.6 3.2 18.3": ["pizzas"], "-1.7 11.7 5.9": ["polarized", "miscued"], "18.0 5.3 -0.3": ["alight"], "8.1 10.0 2.4": ["reclusive"], "9.8 8.5 10.9": ["sterile"], "15.1 35.1 8.8": ["imperialism"], "16.9 8.7 6.2": ["inflate"], "-3.1 3.1 -3.2": ["transactional"], "1.7 6.6 7.3": ["flanker"], "8.6 14.7 1.0": ["unifying"], "0.9 7.3 7.8": ["indulging"], "4.9 7.4 3.3": ["instructing"], "5.5 8.7 0.4": ["frontrunner"], "70.4 8.8 13.4": ["behemoth"], "2.2 10.5 -4.9": ["tirelessly"], "14.4 2.3 -0.4": ["catapulted"], "2.1 14.6 11.7": ["nodes"], "-10.9 6.0 3.2": ["relapse"], "5.7 -4.5 0.3": ["quashed"], "-2.8 -0.9 2.2": ["docket"], "5.1 11.2 2.8": ["expressive"], "5.6 6.6 2.7": ["informally"], "-1.1 12.3 6.6": ["wideout"], "0.3 10.7 6.4": ["hesitated"], "-1.6 9.8 6.6": ["miniseries"], "21.9 5.8 4.1": ["drugmaker"], "10.2 11.8 -1.4": ["whistleblower"], "4.7 8.2 0.7": ["indecent"], "15.1 10.2 9.3": ["rafters"], "9.2 1.3 14.1": ["strand"], "8.6 17.5 1.5": ["bloodiest"], "-3.3 2.2 -1.7": ["roughed"], "16.0 11.2 17.0": ["dynamite"], "11.6 29.2 12.3": ["arrows"], "14.3 3.3 4.4": ["shrouded"], "1.0 10.5 3.9": ["conserving"], "5.2 11.9 10.4": ["stepmother"], "13.0 6.4 6.0": ["widgets"], "10.0 -4.3 8.2": ["culminate"], "-4.0 5.8 7.1": ["reassess"], "14.7 -2.8 2.9": ["flocking"], "-0.6 9.9 5.7": ["columnists"], "-1.5 8.9 3.5": ["psychiatry"], "13.8 10.9 0.6": ["cowboys"], "1.0 4.5 7.5": ["sunscreen"], "-0.2 9.5 5.5": ["compose"], "-9.3 2.7 0.1": ["confer"], "4.8 1.3 3.7": ["tweaks"], "13.7 12.9 0.5": ["erstwhile"], "10.3 4.7 12.5": ["sculptor"], "7.9 10.0 7.0": ["alpha"], "9.1 5.6 12.0": ["laborer"], "-1.6 10.7 -3.0": ["categorically"], "-3.4 2.7 4.8": ["remodel"], "2.4 5.0 -0.9": ["discerning"], "-0.6 6.9 -1.1": ["motivational"], "3.7 6.5 10.0": ["overlay"], "12.5 23.1 10.8": ["lust"], "-3.5 -1.8 2.2": ["delve"], "10.4 1.4 1.0": ["outperforming"], "12.8 3.8 6.0": ["blond"], "-2.9 5.3 -1.9": ["indebted"], "6.9 5.9 6.6": ["throwback"], "7.5 4.9 4.6": ["brash"], "13.1 6.8 5.8": ["unraveling"], "4.0 7.8 2.1": ["miscues"], "4.0 8.4 6.5": ["iv"], "8.7 9.7 4.3": ["evolves"], "12.4 2.0 -9.0": ["paraded"], "7.2 -0.5 -0.4": ["impairments"], "3.3 17.5 3.7": ["blurred"], "2.4 15.2 7.7": ["depriving"], "4.8 5.0 2.6": ["vulgar"], "15.4 8.6 1.9": ["torrent"], "4.2 13.3 7.8": ["yearning"], "-8.3 5.1 7.2": ["inpatient"], "4.9 15.6 9.4": ["pissed"], "16.6 12.6 2.6": ["unmistakable"], "11.2 -6.3 4.9": ["underpin"], "4.0 21.1 10.5": ["loneliness"], "8.0 15.6 28.4": ["nests"], "-2.5 14.5 9.4": ["pistols"], "3.6 6.6 5.1": ["sketchy"], "5.8 19.9 22.4": ["sonar"], "2.9 -0.1 5.4": ["whittled"], "9.0 3.4 -0.8": ["installs"], "14.0 11.9 11.0": ["stubbornly"], "9.3 -7.4 1.1": ["roped"], "-0.2 16.3 1.6": ["reactive"], "9.4 6.8 24.9": ["bays"], "1.3 12.4 1.2": ["qualms"], "5.3 -2.1 8.0": ["doc"], "-3.8 2.1 4.5": ["repayments"], "8.9 4.7 18.9": ["limestone"], "13.8 -4.8 0.7": ["defrauding"], "7.3 14.8 3.8": ["sighted"], "7.2 6.5 12.6": ["carpenter"], "10.3 10.4 33.2": ["spoon"], "-4.8 18.1 7.7": ["cadet"], "-4.0 8.6 8.5": ["kickoffs"], "22.4 12.0 3.0": ["audacious"], "-2.9 9.1 13.0": ["sportsmen"], "9.0 16.2 6.1": ["patiently"], "13.8 7.0 9.9": ["pensioner"], "18.1 1.0 12.9": ["ish"], "14.8 10.2 3.9": ["enlarge"], "-0.4 2.2 10.7": ["variability"], "3.4 4.9 10.1": ["juries"], "4.1 9.7 10.2": ["prostate"], "2.8 -2.3 22.6": ["servings"], "1.7 11.9 10.5": ["sequels"], "-5.1 12.3 0.9": ["defected"], "11.4 6.0 4.2": ["erotic"], "-0.4 15.7 5.3": ["rebellious"], "-4.3 5.5 9.7": ["resettlement"], "12.7 3.9 13.4": ["doldrums"], "16.5 7.6 9.9": ["rattling"], "4.7 2.4 7.1": ["baths"], "14.4 9.9 7.0": ["obligatory"], "16.9 16.7 12.6": ["mist"], "-1.1 1.2 8.0": ["juggle"], "2.4 16.2 4.5": ["disadvantages"], "4.0 20.4 1.2": ["subdue"], "16.6 0.2 4.2": ["bevy"], "20.7 3.5 20.0": ["booms"], "-0.0 9.0 22.3": ["wetland"], "12.4 2.4 20.5": ["flea"], "-1.3 18.3 2.8": ["drawback"], "7.8 9.1 9.0": ["bazaar"], "3.9 3.0 -2.5": ["furnish"], "5.0 23.8 9.1": ["barbaric"], "2.5 6.6 -1.1": ["flattered"], "-0.5 9.6 1.9": ["disheartening"], "2.7 5.6 22.3": ["leftovers"], "0.6 9.1 -1.2": ["repaying"], "2.2 15.9 22.4": ["harbors"], "3.2 4.3 4.8": ["incensed"], "-4.0 4.0 2.4": ["duplication"], "-5.6 12.5 -2.4": ["contradicts"], "5.3 24.4 9.9": ["citizenry"], "1.8 13.8 -3.7": ["undetected"], "4.4 16.3 8.6": ["unto"], "10.6 0.8 -4.4": ["infringed"], "8.0 12.9 9.1": ["spatial"], "2.4 6.7 10.5": ["insomnia"], "4.6 0.2 -3.1": ["exemplifies"], "4.0 8.8 5.2": ["addictions"], "-3.2 8.3 -4.0": ["mistreated"], "8.8 13.7 5.6": ["multiplied"], "-1.1 6.8 11.9": ["nightlife"], "-0.8 10.5 -4.1": ["refrained"], "6.2 17.2 9.6": ["stockholder"], "6.8 9.5 10.9": ["mediocrity"], "7.7 0.8 -9.6": ["infringe"], "20.8 2.5 -2.9": ["revolutionized"], "8.8 21.8 15.3": ["organism"], "17.3 4.9 5.1": ["blip"], "16.9 21.9 4.4": ["dodging"], "4.9 11.3 -1.3": ["drawbacks"], "-6.6 17.8 8.8": ["partisanship"], "8.5 20.8 11.8": ["sidekick"], "11.8 6.6 5.8": ["erupt"], "1.6 16.7 9.0": ["resent"], "11.0 4.3 8.1": ["boisterous"], "-5.2 12.4 10.7": ["deprivation"], "3.0 17.6 3.3": ["clapping"], "0.9 5.5 12.9": ["tallying"], "-0.5 13.4 -0.8": ["misconceptions"], "2.7 1.7 19.5": ["ammonia"], "-4.1 10.6 8.4": ["hypothermia"], "9.2 11.5 11.4": ["treasured"], "7.7 15.3 0.8": ["censor"], "13.3 4.9 14.6": ["mats"], "6.3 1.3 3.8": ["upsurge"], "14.2 23.4 19.4": ["hawks"], "5.1 -0.2 -4.3": ["mediated"], "12.8 4.8 8.6": ["warehousing"], "12.5 8.1 4.4": ["steamy"], "9.0 19.4 9.0": ["proxies"], "6.8 0.1 8.7": ["contrasted"], "4.4 5.5 8.2": ["prohibitive"], "5.9 14.2 2.2": ["definitively"], "-2.0 14.1 -4.7": ["sleeper"], "4.2 12.4 11.5": ["finesse", "unborn"], "14.8 7.9 4.3": ["scrub"], "-0.7 18.0 5.9": ["booing"], "-4.8 10.4 -2.2": ["fidelity"], "8.2 9.4 7.5": ["fervor"], "0.6 16.8 3.2": ["scapegoat"], "10.7 5.8 8.5": ["faring"], "10.6 26.6 7.8": ["messenger"], "8.2 62.7 6.3": ["adversary"], "20.0 10.2 0.3": ["unprofitable"], "-1.8 13.2 6.6": ["cultivating"], "3.2 -3.5 -2.2": ["firsts"], "-2.0 7.3 17.0": ["herds"], "13.4 3.5 -0.3": ["inventors"], "0.2 4.8 3.9": ["headlining"], "14.5 2.3 6.9": ["halve"], "8.1 7.8 9.3": ["pairings"], "4.9 12.9 10.8": ["hindering", "blastoma"], "-3.4 -6.0 1.2": ["doctoral"], "4.6 37.4 3.3": ["cowardly"], "8.9 2.8 13.1": ["richness"], "8.6 12.8 2.0": ["uncontrolled"], "-5.9 14.1 10.8": ["drawdown"], "-0.3 7.1 11.5": ["euthanasia"], "-0.9 9.1 23.5": ["mulch"], "3.6 11.0 4.0": ["hostess"], "4.1 5.2 4.7": ["scorecard"], "4.3 14.4 -2.3": ["unwavering"], "5.0 5.1 5.6": ["favoritism"], "5.6 6.9 6.6": ["netminder"], "6.9 4.9 2.0": ["tracts"], "3.0 11.5 1.6": ["hereby"], "-7.8 18.9 -0.3": ["principled"], "18.9 33.9 9.7": ["bandits"], "19.7 4.6 14.4": ["ballooning"], "-1.0 7.2 22.5": ["barley"], "3.6 31.0 -1.1": ["martyr"], "5.3 4.6 38.5": ["ginger"], "3.7 -2.3 13.3": ["bubbly"], "22.7 18.3 9.4": ["mythical"], "6.8 24.6 11.3": ["trench"], "10.9 3.4 2.9": ["revitalized"], "10.1 16.2 2.4": ["flares"], "-2.2 13.2 9.3": ["assertive"], "2.1 7.2 7.4": ["oversold"], "4.1 8.4 9.1": ["hasten"], "12.5 6.4 16.7": ["tosses"], "5.8 20.7 4.1": ["smear"], "14.4 10.5 11.7": ["magician"], "8.9 15.6 9.2": ["streaking"], "6.0 15.3 -0.1": ["blinded"], "7.7 24.5 -0.9": ["evils"], "0.1 -1.0 11.1": ["nm"], "2.8 -0.8 1.5": ["forensics"], "-2.1 4.6 -3.1": ["resonates"], "25.6 1.8 18.0": ["bellwether"], "8.4 4.7 14.2": ["tuck"], "2.8 5.2 25.9": ["rib"], "-0.9 -1.7 5.5": ["spas"], "2.1 13.3 7.7": ["deflection"], "-2.0 2.8 5.5": ["dorms"], "1.6 8.9 10.6": ["lament"], "4.6 12.3 3.9": ["surrogate"], "-7.3 14.1 3.8": ["recollection"], "7.4 13.2 6.6": ["geometry"], "-2.2 23.8 10.9": ["pathogens"], "6.8 4.2 4.8": ["programmable"], "-0.3 12.5 6.2": ["appreciating"], "12.3 10.7 7.5": ["tracker"], "12.8 8.0 3.8": ["snatching"], "-4.3 9.5 0.9": ["coerced"], "-6.5 3.0 0.8": ["hedged"], "3.7 6.1 6.7": ["ambience"], "6.9 4.5 7.5": ["geologist"], "-1.5 7.5 5.8": ["reunification"], "-1.0 21.4 8.4": ["disengagement"], "3.9 2.2 -2.1": ["scandalous"], "0.3 1.7 8.0": ["impounded"], "-0.8 8.2 7.1": ["integrators"], "11.3 12.2 -3.5": ["detects"], "9.8 4.7 2.4": ["captivating"], "-2.8 -0.7 3.8": ["revisited"], "18.8 11.1 8.6": ["poking"], "8.3 18.2 9.7": ["encountering"], "2.9 1.8 4.7": ["brushes"], "13.6 21.3 4.1": ["conceivable"], "10.2 15.2 3.0": ["porous"], "-7.2 1.3 4.3": ["airtime", "credentialed"], "4.6 30.4 0.9": ["fascist"], "5.5 6.9 16.1": ["anatomy"], "2.9 -1.9 13.7": ["kilos"], "11.5 -4.2 6.4": ["suspends"], "9.3 3.8 13.7": ["haze"], "6.2 1.3 3.6": ["uplift"], "4.1 14.5 4.3": ["improvised"], "13.2 -5.3 1.8": ["relaunch"], "-1.1 5.6 10.4": ["potash"], "-4.9 5.0 6.2": ["denominations"], "6.7 6.8 -0.8": ["neglecting"], "-1.2 5.6 11.0": ["sandals"], "14.1 16.7 23.2": ["cutter"], "9.8 13.8 2.4": ["whispers"], "11.6 11.2 0.2": ["trampled"], "12.3 6.0 5.9": ["plaguing"], "4.5 12.6 1.7": ["uprisings"], "16.4 12.3 8.4": ["battering"], "3.4 -0.5 4.9": ["bypassed"], "-2.7 0.6 31.0": ["cheeses"], "1.9 32.2 3.2": ["regiment"], "-0.3 4.7 6.6": ["departs"], "9.0 4.5 12.2": ["diabetics"], "7.9 2.2 5.5": ["solvency"], "3.2 12.8 5.8": ["rotated"], "10.0 -1.1 3.1": ["scoffed"], "-5.7 9.6 4.8": ["diagnoses"], "32.3 10.7 16.8": ["dwarf"], "7.2 10.1 4.3": ["corresponds"], "8.3 6.5 1.3": ["forbid"], "0.1 -5.7 1.6": ["internships"], "-0.7 11.9 10.9": ["pollster"], "-3.5 6.4 5.6": ["salaried"], "9.3 8.1 2.9": ["discriminating"], "-11.5 1.1 10.3": ["denim"], "7.1 4.2 15.0": ["barns"], "1.2 13.0 12.3": ["fellows"], "19.2 9.2 5.5": ["chained"], "5.6 2.2 1.8": ["lockers"], "7.2 7.6 -3.6": ["extracts"], "11.1 10.5 4.1": ["hotspot"], "2.5 7.8 7.0": ["ordinarily"], "12.0 -0.5 4.4": ["unraveled"], "20.6 29.0 6.4": ["fortress"], "-2.1 6.5 -3.3": ["alluded"], "13.0 11.6 6.5": ["scarcely"], "1.1 20.6 1.8": ["unwise"], "2.7 9.0 2.5": ["sanctity"], "-3.7 14.7 2.3": ["deport"], "-2.4 1.4 -2.0": ["affirms"], "9.4 9.9 9.2": ["shuffling"], "14.7 -0.3 8.2": ["stripper"], "15.7 8.4 -1.4": ["financiers"], "-2.1 12.2 4.2": ["justifies"], "-5.9 0.9 3.1": ["maturities"], "7.9 6.1 13.5": ["retrieval"], "8.5 3.6 -1.2": ["shone"], "6.8 32.7 4.4": ["bombardment"], "8.1 37.6 -0.4": ["liberate"], "10.4 9.1 13.2": ["hoarding"], "12.6 9.5 11.4": ["twilight"], "-3.8 12.8 11.6": ["droughts"], "-2.8 46.6 9.0": ["militarily"], "8.0 9.5 7.4": ["relishing"], "3.4 2.6 -0.5": ["rung"], "7.9 2.7 12.1": ["riverfront"], "6.0 7.6 2.4": ["hasty"], "12.2 7.0 8.7": ["grassy"], "11.5 18.9 11.3": ["polluters"], "4.7 11.3 8.0": ["mismatch"], "-4.1 3.0 -3.1": ["telephoned"], "8.4 10.9 6.8": ["socializing"], "-3.9 6.9 4.0": ["astute"], "12.4 8.8 12.9": ["beige"], "-2.5 2.9 13.3": ["horticulture"], "6.8 11.5 5.2": ["cordon"], "2.6 4.7 -2.4": ["outlasted"], "-4.2 6.2 8.7": ["adolescence"], "2.3 -0.4 6.1": ["marathons"], "12.1 11.1 -1.6": ["changer"], "14.5 20.3 15.4": ["jaws"], "0.2 11.0 8.6": ["unhappiness"], "8.2 6.7 3.8": ["wannabe"], "0.1 15.7 5.6": ["alienating"], "15.6 8.0 10.4": ["quintessential"], "12.5 20.2 4.0": ["taunting"], "-2.2 9.9 -2.3": ["irons"], "15.1 0.1 3.8": ["swooped"], "10.1 10.5 3.9": ["restatement"], "4.4 7.6 6.2": ["barefoot"], "0.0 1.4 1.1": ["retrofit"], "15.5 2.1 0.0": ["soothe"], "7.1 1.3 8.2": ["mailboxes"], "14.4 12.3 5.2": ["rumble"], "2.0 8.4 2.3": ["specifying"], "4.3 9.2 3.5": ["nicest"], "15.7 5.1 5.4": ["nano"], "0.2 3.1 10.9": ["kosher"], "6.0 8.4 -5.7": ["reorganized"], "9.7 6.2 2.6": ["amplified"], "0.8 12.8 9.9": ["sexes"], "11.0 -0.1 4.8": ["clung"], "-6.8 9.8 8.0": ["shorthanded"], "16.0 1.1 18.5": ["tar"], "6.6 4.9 10.9": ["coax"], "10.1 7.3 6.6": ["tattooed"], "12.7 4.0 5.0": ["equivalents"], "3.4 2.9 1.1": ["handbook"], "15.5 10.9 3.1": ["spectacularly"], "14.5 -0.1 6.8": ["overblown"], "14.0 15.8 21.0": ["rodents"], "-1.6 6.9 5.2": ["err"], "0.4 18.7 22.5": ["coyotes"], "2.7 2.5 8.9": ["flute"], "13.2 12.0 0.3": ["smoldering"], "6.2 16.5 5.6": ["obnoxious"], "5.0 7.8 -6.2": ["discreet"], "6.9 14.9 7.3": ["psychic"], "3.9 19.8 2.3": ["consciously"], "-8.3 5.4 5.0": ["songwriters"], "4.7 2.1 3.1": ["unsuitable"], "2.0 10.1 9.2": ["flicks"], "10.6 9.1 10.7": ["colon"], "-0.6 4.0 12.0": ["tendon"], "8.2 3.2 11.9": ["exuberant"], "2.9 9.7 29.1": ["blooms"], "8.3 5.4 10.2": ["postcard"], "3.3 23.6 7.1": ["boredom"], "-3.6 4.4 4.6": ["stylist"], "4.7 14.4 1.2": ["flushed"], "10.2 8.9 9.0": ["busts"], "12.8 -2.2 12.1": ["piping"], "3.0 5.4 2.4": ["furthering"], "10.3 6.6 5.6": ["fondness"], "26.5 -1.2 10.3": ["gleaming"], "3.1 5.0 3.4": ["fondly"], "7.7 9.5 3.6": ["garb"], "1.7 9.3 10.7": ["sensibility"], "-5.9 3.8 16.7": ["stormwater"], "2.5 1.8 8.7": ["artworks"], "-0.9 4.5 1.1": ["assesses"], "12.9 12.3 3.3": ["headwinds"], "5.2 22.7 11.3": ["bluff"], "18.1 10.3 6.5": ["symbolizes"], "11.0 -1.3 6.6": ["overshadow"], "9.2 1.0 -2.7": ["notches"], "5.0 5.4 -2.9": ["rupture"], "12.0 -2.9 7.0": ["underweight"], "3.3 21.8 5.5": ["disabling"], "15.3 7.9 4.0": ["schoolboy"], "10.8 14.5 14.2": ["decoration"], "12.6 -5.4 -0.2": ["wowed"], "9.7 8.2 5.0": ["brushing"], "28.6 5.7 5.5": ["powerhouses"], "0.9 2.2 7.2": ["consignment"], "2.1 13.6 6.9": ["cocky"], "-1.7 7.0 8.3": ["timelines", "autophagic"], "-5.3 5.2 0.4": ["rehabilitated"], "4.0 11.6 7.5": ["philosopher"], "6.7 6.3 4.0": ["carpets"], "-3.7 -0.4 10.0": ["townhouse"], "1.3 0.6 14.7": ["reclamation"], "11.5 12.4 0.1": ["loudest"], "4.8 36.8 3.3": ["assassin"], "12.9 8.8 8.9": ["vanish"], "1.7 16.1 14.4": ["rangers"], "5.1 7.7 2.6": ["jog"], "5.4 5.9 6.9": ["bladder"], "17.4 1.8 3.6": ["loomed"], "2.2 11.8 25.8": ["rum"], "-0.3 1.5 8.2": ["soprano"], "6.8 4.4 -2.3": ["foresight"], "7.0 9.0 21.4": ["charcoal"], "14.3 1.1 7.8": ["offload"], "4.5 10.3 41.0": ["peas"], "11.6 14.0 9.4": ["magnified"], "7.1 9.6 2.1": ["injures"], "13.8 -4.6 6.2": ["bucked"], "4.8 10.9 12.4": ["hydrocarbons"], "2.0 -6.2 2.2": ["roundtable"], "20.8 -3.7 -4.4": ["adverts"], "4.9 3.4 0.9": ["dribbled"], "9.2 11.4 7.1": ["afterthought"], "13.4 9.1 13.0": ["crumble"], "15.0 0.1 7.3": ["capsules"], "-0.0 6.8 -5.0": ["combing"], "10.4 10.7 -2.2": ["emitted"], "-4.7 11.5 6.6": ["carbohydrates"], "14.6 23.3 11.6": ["asteroid"], "8.8 7.8 11.4": ["bourses"], "33.5 8.6 11.2": ["inflatable"], "6.3 7.6 13.3": ["bruise"], "-5.0 -3.0 1.8": ["timeliness"], "8.5 0.4 2.8": ["attendants"], "17.8 12.8 10.9": ["feeble"], "-1.6 3.4 5.1": ["stipulation"], "9.0 10.8 36.7": ["carp"], "8.9 -0.2 35.2": ["noodles"], "0.9 0.1 6.9": ["pent"], "6.6 6.7 2.9": ["seams"], "13.0 8.5 17.7": ["delights"], "-4.0 8.3 4.2": ["cordial"], "-7.7 9.5 4.0": ["quorum"], "10.6 25.5 6.0": ["oncoming"], "8.1 24.4 6.8": ["looters"], "-1.0 2.0 6.2": ["frugal"], "0.1 5.7 4.4": ["cessation"], "6.0 0.2 13.4": ["biennial"], "-1.3 4.9 5.6": ["eldest"], "13.8 8.5 7.8": ["reverses"], "5.3 10.2 12.0": ["fuselage"], "-3.5 1.7 -0.1": ["affords"], "-3.6 2.2 9.5": ["outflows"], "7.4 9.8 -0.1": ["comprehensively"], "-4.3 12.1 -6.3": ["disseminate"], "15.6 1.9 3.7": ["apex"], "17.8 3.2 1.4": ["offshoot"], "6.2 7.1 6.9": ["lukewarm"], "5.2 4.3 14.7": ["refrigeration"], "-6.7 12.4 1.2": ["attaining"], "2.3 0.1 -2.1": ["kudos"], "2.8 21.5 12.7": ["persuasion"], "9.8 20.4 13.0": ["lever"], "12.9 1.6 1.6": ["brimming"], "2.5 14.3 1.3": ["extradite"], "6.5 12.1 11.2": ["walker"], "7.1 5.8 10.3": ["membrane"], "11.6 8.9 -0.2": ["mishaps"], "3.3 11.7 10.5": ["cleanly"], "2.9 11.0 1.5": ["illiterate"], "9.1 6.1 3.8": ["effortless"], "8.0 6.8 69.1": ["oyster"], "2.6 10.7 2.2": ["warmly"], "-7.0 6.9 -2.0": ["abstain"], "10.2 5.0 10.0": ["webcam"], "15.9 10.2 4.5": ["flung"], "-7.0 4.7 -1.7": ["instilled"], "7.8 -0.1 4.7": ["boycotting"], "5.4 7.3 7.4": ["uniqueness"], "0.8 15.6 1.5": ["pollsters"], "11.8 7.9 6.9": ["shambles"], "-1.5 8.4 10.0": ["blanks"], "10.8 3.6 5.5": ["loops"], "12.6 16.0 6.1": ["radius"], "10.2 5.6 2.8": ["inserting"], "-3.1 8.4 7.4": ["misrepresent"], "5.3 19.2 5.4": ["annoyance"], "0.1 3.4 0.6": ["cartridges"], "12.2 25.0 14.6": ["vampires"], "6.4 15.7 1.0": ["obsessive"], "9.7 15.1 13.6": ["butts"], "0.3 22.2 3.1": ["impediment"], "6.2 16.2 2.8": ["rapist"], "2.1 9.2 9.7": ["homebuilders"], "2.0 4.1 15.8": ["milder"], "-0.7 14.3 -2.9": ["unequivocal"], "-1.7 5.2 11.6": ["matinee"], "-3.7 13.9 10.8": ["cornerbacks"], "18.4 -6.5 3.5": ["quadrupled"], "6.1 8.3 2.4": ["snuck"], "-5.8 2.4 3.3": ["artistes"], "13.2 9.6 13.8": ["crystals"], "-2.9 4.1 3.9": ["aggrieved"], "15.4 7.1 9.5": ["pseudo"], "6.3 6.2 -7.3": ["misusing"], "10.9 8.0 2.8": ["rejuvenated"], "1.6 13.1 6.9": ["southpaw"], "-4.1 10.6 -1.5": ["consensual"], "5.4 10.6 7.3": ["pauses"], "3.7 26.5 -0.1": ["infiltrate"], "7.1 20.2 4.8": ["manifestation"], "-0.5 1.3 -1.8": ["standardization"], "-0.3 22.2 3.4": ["unequivocally"], "8.3 26.2 10.0": ["indiscriminate"], "5.3 1.6 6.9": ["shutdowns"], "13.2 10.0 28.7": ["shipbuilding"], "-2.3 7.7 2.5": ["obituary"], "4.8 8.5 4.9": ["hustled"], "12.0 3.2 4.1": ["stashed"], "6.7 2.7 7.4": ["cooperatives"], "2.5 5.4 12.1": ["painters"], "4.7 8.0 28.2": ["vinegar"], "-5.5 -5.5 2.7": ["stipend"], "-4.9 -0.5 4.0": ["revocation"], "5.7 11.2 -7.9": ["saluted"], "4.4 -6.4 0.2": ["recorders"], "12.2 12.3 8.8": ["stink"], "10.0 17.4 4.3": ["chore"], "-4.2 7.3 2.1": ["miscarriage"], "1.3 1.1 4.3": ["dryer"], "6.2 5.0 6.9": ["proprietor"], "10.5 11.6 6.4": ["pirated"], "7.3 12.2 7.3": ["adjusts"], "2.4 4.2 9.5": ["hepatitis"], "2.8 1.1 12.9": ["equine"], "5.3 0.8 -3.0": ["personalization"], "5.2 12.8 7.5": ["environmentalist"], "-7.2 20.4 -1.2": ["detachment"], "4.9 14.8 5.2": ["moviegoers"], "2.4 5.2 16.7": ["bathing"], "2.0 14.2 7.0": ["justifying"], "9.4 -4.6 -5.2": ["defrauded"], "2.2 -0.1 6.0": ["commenters"], "-4.0 3.8 4.7": ["remedial"], "0.5 9.7 6.4": ["semblance"], "0.4 4.7 4.3": ["rites"], "4.1 7.9 8.7": ["nutshell"], "1.5 15.5 12.6": ["elbows"], "13.7 9.2 2.4": ["scorching"], "7.0 3.6 42.5": ["cabbage"], "17.0 17.8 3.8": ["perils"], "3.8 -2.9 18.0": ["earrings"], "12.1 15.8 8.4": ["obscured"], "2.9 30.2 6.1": ["inflicting"], "6.5 1.9 -4.2": ["examiner"], "11.5 8.1 32.4": ["bean"], "9.9 20.3 15.4": ["emperor"], "4.1 10.1 8.5": ["hydrocarbon"], "7.4 5.4 5.4": ["donning"], "-7.4 3.4 -1.4": ["unmet"], "8.6 1.2 0.3": ["scoured"], "-1.6 3.7 0.5": ["handwriting"], "4.4 27.6 10.6": ["progressives"], "1.0 13.9 2.5": ["abiding"], "1.7 14.4 1.0": ["coalitions"], "-1.0 10.3 18.7": ["cruisers"], "11.9 15.3 10.5": ["awkwardly"], "-3.2 8.2 6.4": ["adhering"], "5.1 15.1 12.5": ["cronies"], "-9.9 1.3 -0.8": ["abstained"], "3.5 5.8 24.0": ["beachfront"], "0.4 20.4 -0.9": ["collaborator"], "-1.5 12.8 5.3": ["formulating"], "4.2 7.5 9.9": ["perk"], "9.7 19.7 6.2": ["paradox"], "0.9 3.3 12.5": ["midpoint"], "21.1 7.9 2.7": ["readying"], "7.4 13.9 13.0": ["fuck"], "-4.1 2.3 8.0": ["sanitary"], "10.4 -3.7 5.7": ["firmed"], "6.1 16.0 11.3": ["charms"], "-4.5 -2.5 -1.4": ["expiry"], "10.6 2.3 8.9": ["paraphernalia"], "2.0 5.7 3.1": ["feuding"], "14.2 20.9 18.3": ["microbes"], "9.1 8.9 4.0": ["irate"], "8.5 12.3 5.0": ["shred"], "3.5 10.1 7.9": ["sprinters"], "-3.1 9.9 3.2": ["paperback"], "-5.5 0.1 -2.5": ["formulations"], "-2.3 17.1 4.2": ["alienate"], "8.9 16.6 7.0": ["subtly"], "4.3 1.4 13.4": ["shortening"], "-3.9 14.7 9.9": ["nonviolent"], "15.7 10.2 15.4": ["explorers"], "8.9 11.6 6.1": ["banished"], "3.4 7.9 12.3": ["fats"], "13.2 9.4 5.1": ["intertwined", "arrythmia"], "-3.6 8.8 7.8": ["detentions"], "1.9 4.0 6.1": ["ejection"], "0.6 1.4 0.9": ["stimulated"], "7.4 10.0 8.2": ["stagnation"], "-3.4 3.5 5.4": ["minicamp"], "4.3 20.6 5.7": ["innate"], "-2.9 8.5 13.2": ["idling"], "4.6 6.4 4.5": ["clearances"], "0.4 10.4 17.3": ["palate"], "4.4 6.9 12.7": ["tailgate"], "1.9 8.3 17.7": ["shin"], "11.7 4.7 4.2": ["removable"], "-1.1 7.2 0.4": ["relive"], "4.5 10.9 12.3": ["palette"], "9.9 17.8 13.0": ["pastime"], "17.9 11.8 9.3": ["sickening"], "4.2 3.1 -0.5": ["gateways"], "-2.9 5.3 13.1": ["lifeguards"], "9.2 13.2 6.8": ["stamping"], "6.7 14.0 1.7": ["electrifying"], "6.2 0.6 8.8": ["curbed"], "6.4 9.9 -1.6": ["unites"], "-1.6 18.1 15.1": ["ranger"], "4.7 10.4 10.6": ["egos"], "8.2 14.0 25.4": ["olive"], "-7.0 3.7 13.1": ["palladium"], "3.4 1.2 3.8": ["stiffness"], "13.5 12.2 3.0": ["feats"], "11.4 8.9 9.4": ["dreary"], "5.2 1.3 10.1": ["palatable"], "2.7 7.3 7.2": ["wooded"], "6.9 7.7 13.1": ["cardinals"], "9.1 18.5 7.9": ["horribly"], "1.8 9.6 2.4": ["tirade"], "15.1 7.5 11.3": ["waterfall"], "6.2 6.1 14.3": ["jewels"], "21.8 12.0 8.1": ["clowns"], "-1.2 -0.1 11.9": ["bales"], "17.6 1.3 10.1": ["nudged"], "-0.6 13.7 28.7": ["sauces"], "-1.0 6.3 1.9": ["reigns"], "9.9 14.0 35.4": ["spawning"], "5.2 11.9 11.5": ["sensibilities"], "-3.0 15.5 -0.4": ["liquidate"], "3.0 16.7 -1.9": ["regrouped"], "-18.6 3.1 3.1": ["absences"], "-1.4 15.2 -6.6": ["uncompromising"], "8.0 14.2 -1.2": ["immersive"], "16.3 11.0 31.4": ["fry"], "-0.6 14.5 16.2": ["sweetness"], "0.6 7.0 10.5": ["modem"], "0.0 13.5 8.7": ["mis"], "3.6 13.9 -5.1": ["ardent"], "-6.0 2.0 9.1": ["alternates"], "-6.7 13.3 4.2": ["sympathize"], "-1.2 11.0 5.2": ["aggravating"], "6.2 10.6 7.7": ["fathom"], "3.8 7.0 7.3": ["hi"], "2.0 17.4 8.3": ["aggressiveness"], "17.0 12.5 10.8": ["stomping"], "7.1 7.8 -5.2": ["whisked"], "20.5 11.0 -0.1": ["aloft"], "15.3 4.4 2.8": ["programmer"], "13.0 7.8 7.1": ["outlandish"], "1.5 6.8 4.1": ["normalization"], "8.3 -1.7 3.3": ["cautionary"], "9.7 8.5 6.2": ["fades"], "2.2 18.5 9.7": ["cursing"], "-0.1 11.8 -4.1": ["qualitative"], "5.4 1.9 13.4": ["lighten"], "2.9 24.4 -1.1": ["hateful"], "1.1 14.4 5.9": ["tranquility"], "-3.8 3.0 11.7": ["reunions"], "7.5 14.2 -4.4": ["torturing"], "-5.4 12.3 9.8": ["monologue"], "4.5 24.8 1.7": ["intolerable"], "13.5 10.8 18.2": ["butcher"], "-7.3 11.9 10.3": ["priesthood"], "5.5 2.4 4.9": ["matures"], "12.9 3.1 7.8": ["frenetic"], "12.7 8.4 11.3": ["chewing"], "10.0 16.9 2.5": ["rabid"], "6.7 15.3 3.6": ["ducked"], "0.4 2.1 9.3": ["vascular"], "9.6 12.1 5.7": ["sweaty"], "9.7 -0.5 10.4": ["lipstick"], "4.1 1.1 3.9": ["evoked"], "-5.4 5.7 11.6": ["sightseeing"], "5.6 8.1 13.1": ["iced"], "5.2 9.1 3.1": ["coldest"], "15.2 7.0 7.9": ["stalwarts"], "4.5 1.7 11.2": ["shuttles", "lista"], "-3.8 12.3 3.6": ["sodomy"], "13.8 7.2 27.1": ["specimen"], "2.9 9.5 10.9": ["lesions"], "3.7 5.2 0.9": ["conceive"], "8.9 22.0 0.4": ["rioters"], "-2.6 0.7 2.2": ["complimented"], "8.0 17.7 3.3": ["thirsty"], "-2.5 10.8 2.3": ["betterment"], "1.0 9.3 5.0": ["heartache"], "2.5 10.6 12.1": ["retreats"], "11.0 23.8 6.0": ["tribesmen"], "27.0 10.4 -0.4": ["multinationals"], "8.0 12.0 15.2": ["undersized"], "-6.3 3.6 9.6": ["underclassmen"], "11.5 4.6 21.0": ["kitten"], "-3.5 10.6 1.8": ["interoperable"], "17.3 4.2 5.5": ["illustrating"], "14.7 -3.4 2.1": ["fizzled"], "2.9 12.6 7.2": ["inscribed"], "25.5 2.3 10.0": ["showpiece"], "14.7 6.7 6.9": ["aficionados"], "9.0 6.1 7.9": ["clustered", "lixisenatide"], "-7.0 10.3 0.3": ["medalist"], "5.9 1.5 5.4": ["robes"], "-1.2 4.2 1.4": ["versed"], "2.1 9.9 -4.1": ["bloodstream"], "5.7 2.6 0.7": ["snapshots"], "6.1 2.0 6.3": ["handball"], "0.1 -0.6 8.5": ["apprenticeship"], "1.7 23.8 6.1": ["rhetorical"], "-1.2 22.3 6.5": ["brotherhood"], "10.8 12.0 15.1": ["palms"], "9.9 -1.4 9.3": ["spurs"], "2.8 14.4 -0.1": ["comforted"], "-6.4 9.2 8.9": ["outfielders"], "-4.6 3.0 -2.4": ["firmware"], "15.9 6.9 3.2": ["attaches"], "12.5 6.1 8.0": ["jetliner"], "13.9 3.7 10.9": ["tram"], "26.3 11.2 8.6": ["swallowing"], "4.2 10.2 4.1": ["sewers"], "5.2 7.9 7.6": ["stifled"], "5.2 5.8 12.4": ["smoky"], "3.2 8.4 10.1": ["acne"], "14.2 12.8 1.4": ["illuminate"], "13.9 8.4 2.2": ["searing"], "0.6 3.5 4.1": ["radiology"], "13.1 15.0 6.8": ["stun"], "3.4 -3.4 -1.1": ["workstations"], "13.2 4.2 -0.3": ["stranglehold"], "2.0 4.8 1.1": ["conclusive"], "-1.1 3.3 4.5": ["interconnect"], "7.0 3.2 9.9": ["transplanted"], "8.1 8.2 14.0": ["shovels"], "7.3 7.1 -0.1": ["evokes"], "-3.1 5.1 5.7": ["coupe"], "10.2 16.7 -3.2": ["taunted"], "-3.3 1.2 2.2": ["violinist"], "7.2 1.6 5.4": ["murals"], "-0.1 1.9 4.3": ["overruled"], "0.1 7.8 4.5": ["generics"], "13.4 18.5 9.0": ["cheats"], "1.0 7.1 4.3": ["misgivings"], "-7.0 11.3 11.5": ["motorcyclists"], "0.1 5.6 6.4": ["librarians"], "10.0 32.5 8.8": ["intruders"], "5.3 5.6 0.6": ["personalize"], "2.6 0.5 4.6": ["mishandled"], "2.9 2.2 3.3": ["terminating"], "3.8 -0.8 -4.5": ["breezed"], "13.3 8.5 10.8": ["umbrellas"], "2.0 11.9 -4.8": ["loudspeakers"], "6.5 12.3 12.8": ["whim"], "-1.5 5.0 7.0": ["formality"], "-4.4 25.6 2.2": ["informants"], "30.0 7.1 7.8": ["skyscraper"], "-0.6 12.5 1.7": ["reflections"], "1.4 14.4 4.1": ["mowing"], "14.4 15.1 20.9": ["donkey"], "-6.2 1.7 7.4": ["antidepressants"], "0.3 -1.4 -1.6": ["rigors"], "4.8 17.2 10.3": ["confronts"], "-0.9 1.8 5.2": ["outputs"], "6.0 11.7 2.7": ["dynamically"], "2.2 3.8 0.4": ["laurels"], "10.8 21.4 13.3": ["underworld"], "-3.3 17.7 -2.7": ["disservice"], "8.7 2.9 0.6": ["endowed"], "6.6 2.6 14.6": ["rustic"], "11.1 2.3 3.0": ["foyer"], "9.2 -0.3 -1.5": ["quash"], "9.5 9.7 5.3": ["jarring"], "8.3 4.3 6.3": ["pronounce"], "-4.3 5.5 9.0": ["javelin"], "9.3 12.3 8.8": ["wagons"], "6.1 4.3 15.2": ["pulses"], "11.5 7.3 12.0": ["eh"], "-2.2 19.3 9.2": ["cohorts"], "11.0 9.4 19.0": ["lunar"], "5.5 10.2 7.7": ["meticulously"], "11.7 19.5 9.5": ["mythology"], "-8.3 15.5 0.0": ["spiritually"], "3.6 1.8 -0.7": ["eventful"], "12.1 8.3 9.6": ["plumber"], "8.7 0.3 9.9": ["sparkle"], "5.1 12.5 9.6": ["warmup"], "3.7 14.4 -2.0": ["secondly"], "-11.4 8.4 4.8": ["musically"], "3.6 17.6 4.6": ["raiding"], "1.7 15.8 9.7": ["needlessly"], "5.6 7.8 -3.3": ["detectors"], "9.4 11.2 1.7": ["cede"], "0.5 2.5 -1.9": ["videotapes"], "0.5 14.0 2.2": ["strayed"], "1.2 3.7 7.5": ["cereals"], "19.3 12.4 6.9": ["furiously"], "8.3 16.2 5.8": ["awakening"], "1.5 9.5 8.1": ["brag"], "-3.0 1.1 16.7": ["annuities"], "-2.9 1.5 35.2": ["peppers"], "5.4 6.0 9.6": ["fluctuating"], "12.4 1.8 5.7": ["approx"], "-3.1 8.9 8.1": ["melodic"], "0.6 8.8 8.3": ["perpetuate", "rebalance"], "-2.6 18.4 5.1": ["wingers"], "11.5 8.9 4.5": ["insuring"], "16.7 0.2 6.4": ["halts"], "-5.7 2.1 9.3": ["clunkers"], "0.7 6.8 4.8": ["canvassing"], "13.1 8.6 6.8": ["bounded"], "9.2 4.1 5.9": ["realty"], "5.9 7.5 12.7": ["refs"], "8.0 2.0 12.5": ["loosened"], "4.8 17.3 9.9": ["lob"], "-1.6 -0.8 5.4": ["gymnasts"], "13.1 2.6 -4.1": ["enviable"], "-1.8 5.5 9.9": ["fillies"], "-7.4 5.3 1.3": ["storylines"], "1.6 0.9 10.3": ["knit"], "8.3 4.2 17.4": ["coke"], "5.9 19.7 7.9": ["binoculars"], "-1.5 11.7 5.2": ["surname"], "15.8 9.3 3.9": ["grisly"], "11.0 -3.7 -2.8": ["mooted"], "1.1 5.2 14.7": ["vegan"], "2.8 6.3 3.7": ["metabolic"], "-7.0 1.0 5.6": ["delinquencies"], "4.1 12.7 8.8": ["locales"], "6.0 -2.1 10.5": ["aggregation"], "8.1 3.4 6.0": ["premiers"], "7.6 5.4 30.9": ["angling"], "1.4 4.2 8.1": ["warmest"], "5.5 -3.2 8.0": ["fuller"], "11.4 9.5 18.9": ["pellets"], "-0.3 2.7 34.2": ["ivory"], "4.7 5.5 5.6": ["rancher"], "-1.2 -4.1 0.0": ["benefitted"], "26.0 9.4 8.9": ["crazed"], "-0.5 -4.2 0.8": ["preparatory"], "10.4 2.9 6.7": ["swiped"], "-0.9 13.0 6.3": ["harsher"], "-4.1 6.2 29.2": ["soups"], "15.3 8.2 16.1": ["smothered"], "8.4 0.5 -1.3": ["devoting"], "3.3 5.8 1.4": ["clashing"], "8.6 6.1 6.3": ["righthander"], "9.8 11.6 11.1": ["piercing"], "6.5 2.4 6.7": ["serene"], "9.4 -0.5 -3.5": ["objecting"], "2.6 25.3 10.4": ["prejudices"], "7.8 11.0 6.6": ["stepson"], "-3.2 16.1 5.7": ["unoccupied"], "11.0 1.0 -1.5": ["breathed"], "-7.5 -2.4 1.5": ["concurred"], "3.0 8.5 7.2": ["carjacking"], "5.4 25.2 0.5": ["unprotected"], "1.2 23.6 1.0": ["isolating"], "0.4 6.7 7.6": ["thresholds"], "-2.8 9.4 0.9": ["eloquent"], "-3.1 11.3 -0.2": ["unchallenged"], "-3.2 13.9 5.3": ["jeep"], "12.4 6.5 5.0": ["overlooks"], "7.4 -0.5 4.9": ["receded"], "9.6 24.7 1.6": ["bravely"], "0.7 4.0 2.2": ["solicitors"], "-1.8 7.8 1.7": ["hilly"], "2.1 5.5 -3.9": ["meningitis"], "0.5 9.2 5.6": ["infraction"], "4.3 4.3 5.1": ["precautionary"], "5.6 1.6 2.4": ["tremors"], "-12.2 6.9 10.8": ["homeownership"], "-1.8 15.2 5.0": ["misconception"], "-5.6 9.6 2.9": ["camcorder"], "8.4 1.7 8.4": ["mums"], "9.8 0.3 6.8": ["clamped"], "0.3 0.2 10.1": ["frameworks"], "-4.0 3.3 11.4": ["ag"], "10.5 5.9 12.8": ["plaster"], "9.7 2.6 1.1": ["unsealed"], "-5.2 20.3 11.1": ["lefties"], "-2.1 16.5 5.1": ["intelligently"], "-3.8 8.2 -3.4": ["rebuttal"], "10.1 -2.3 3.5": ["upholds"], "-2.5 5.7 5.9": ["timeouts"], "0.1 7.4 2.7": ["franchisee"], "4.4 9.2 -4.4": ["mourned"], "-2.6 3.8 4.4": ["exercisable"], "6.9 18.7 -8.1": ["equipping"], "-4.0 6.5 3.9": ["nuanced"], "12.5 7.3 22.1": ["hamburgers"], "7.4 13.9 8.8": ["congresswoman"], "-4.5 10.4 6.2": ["latency"], "-0.7 -1.9 4.0": ["custodial"], "-2.7 8.0 64.7": ["shellfish"], "-4.4 9.5 0.8": ["rehearsing"], "5.2 12.4 5.1": ["holdout"], "-2.3 -0.6 6.4": ["nonmembers"], "-2.7 1.7 16.5": ["freshness"], "3.9 9.7 17.7": ["felons"], "8.1 9.0 0.1": ["charger"], "4.6 3.9 14.6": ["blossom"], "2.6 5.0 -2.1": ["singling"], "9.2 3.8 5.9": ["satirical"], "-3.3 8.6 2.3": ["disapprove"], "11.0 8.8 4.6": ["widget"], "5.4 10.8 4.3": ["demolishing"], "12.8 17.4 5.7": ["enigmatic"], "3.7 8.4 4.9": ["excels"], "14.0 8.1 8.1": ["wallpaper"], "14.1 1.4 16.8": ["chrome"], "7.5 8.6 5.1": ["analogue"], "6.5 7.5 3.7": ["mobbed"], "1.2 3.8 9.9": ["pastures"], "1.6 5.5 8.9": ["buttocks"], "-1.0 17.7 12.4": ["crossfire"], "-3.4 11.0 3.8": ["contemporaries"], "1.1 4.3 14.7": ["farmed"], "18.3 2.9 2.5": ["cranked"], "9.6 2.2 -2.9": ["profited"], "11.6 -3.2 5.7": ["cancels"], "10.1 2.6 2.2": ["excite"], "-1.0 -4.1 4.5": ["ppm"], "-0.6 6.0 -1.2": ["easement"], "-3.4 1.4 0.5": ["psychiatrists"], "14.7 5.9 6.2": ["overheated"], "9.5 6.1 13.8": ["plantations"], "-0.2 3.7 6.6": ["generational", "synchronizations"], "6.3 7.1 12.3": ["foundry"], "9.9 9.4 14.8": ["ram", "sapota"], "2.7 13.2 24.3": ["vines"], "10.5 10.1 8.4": ["sensory"], "3.1 3.3 7.7": ["surcharges"], "13.0 13.1 79.2": ["crabs"], "2.0 3.9 1.5": ["unhurt"], "8.0 22.0 7.6": ["overpowering"], "2.7 14.7 7.7": ["seam"], "7.3 5.0 13.0": ["artistry"], "2.9 14.6 4.2": ["discern"], "2.9 7.0 2.5": ["subset"], "0.8 4.5 1.6": ["defaulting"], "4.4 2.5 4.6": ["factoring"], "-2.7 7.3 3.8": ["recounting"], "6.8 3.7 5.8": ["undergoes"], "4.7 12.8 25.2": ["glacier"], "7.8 18.4 4.2": ["sheltering"], "11.5 4.7 9.4": ["ornate"], "3.3 12.5 1.4": ["cleansing"], "3.7 21.8 12.4": ["inhumane"], "-3.6 -0.4 -0.9": ["consultative"], "-0.1 7.3 4.3": ["forwarding"], "10.6 0.3 8.2": ["galvanized"], "-4.7 3.8 5.6": ["choral"], "2.0 0.4 -2.6": ["misrepresented"], "15.5 4.2 1.6": ["shabby"], "17.4 17.5 -0.1": ["blindfolded"], "10.8 15.1 3.4": ["stench"], "7.3 8.7 10.9": ["resultant"], "8.8 10.9 13.7": ["aroma"], "3.4 0.9 4.3": ["submits", "tation"], "22.1 5.8 3.2": ["watchdogs"], "-2.7 6.5 2.0": ["unsatisfactory"], "9.3 10.7 2.7": ["fruitless"], "8.4 10.2 -7.5": ["wirelessly"], "7.5 -3.3 13.4": ["doled"], "17.4 11.8 7.0": ["mangled"], "6.8 -0.3 10.8": ["loosening"], "6.8 10.4 2.3": ["sobbing"], "10.1 11.2 5.3": ["shocker"], "-2.4 15.8 0.9": ["grieve"], "-3.6 7.0 8.7": ["feedstock"], "12.7 7.7 4.4": ["predominant"], "4.6 0.1 3.1": ["dailies"], "-3.3 1.6 -6.3": ["clarifying"], "-0.9 -2.4 8.6": ["moderating"], "-5.6 11.9 2.5": ["avenged"], "14.5 20.3 -2.0": ["fanatic"], "-2.0 10.0 10.9": ["humanities"], "11.8 13.2 2.0": ["blunders"], "-0.5 4.1 0.8": ["individualized"], "16.6 15.5 10.6": ["fickle"], "3.4 13.9 11.5": ["pleasures"], "5.8 9.6 6.3": ["shrewd"], "12.0 4.5 4.3": ["ragged"], "20.5 4.0 7.4": ["mania"], "4.6 11.2 0.9": ["extort"], "1.9 18.7 -8.0": ["massacres"], "5.1 1.0 -0.9": ["obscurity"], "2.7 9.9 6.8": ["invoking"], "9.4 6.7 12.2": ["grandkids"], "5.3 16.9 5.7": ["exaggeration"], "-6.0 17.7 1.8": ["hurtful"], "0.0 16.1 -6.5": ["comforts"], "-2.1 22.3 -3.5": ["follower"], "3.0 11.4 8.1": ["footballing"], "7.6 -0.7 1.4": ["chemist"], "10.8 11.2 3.5": ["gaffe"], "5.4 12.1 1.1": ["powerfully", "sherpa"], "3.3 7.3 8.9": ["burdensome"], "11.2 5.6 1.2": ["recapitalization"], "-2.8 11.0 16.5": ["tonnage"], "-3.4 11.5 5.5": ["geographies"], "6.8 -0.0 5.5": ["stumped"], "-0.4 1.0 6.6": ["advisories"], "-1.4 4.0 12.2": ["hydropower"], "8.2 8.5 23.8": ["lagoon"], "16.0 11.5 9.9": ["dripping"], "-1.4 7.5 13.1": ["ration"], "20.1 5.8 9.6": ["teeming"], "0.2 -3.1 4.1": ["lecturers"], "1.0 10.6 8.2": ["driveways"], "-7.7 17.4 -1.2": ["unselfish"], "13.4 14.0 9.7": ["pixel"], "6.1 0.8 40.7": ["strawberry"], "4.7 8.4 3.7": ["speechless"], "1.4 4.4 -1.0": ["kms"], "11.3 4.9 3.3": ["torrid"], "2.4 6.1 5.2": ["mistrial"], "7.0 7.7 1.9": ["ve"], "11.6 18.5 15.9": ["nuke"], "2.0 12.8 6.7": ["endearing"], "-4.9 4.8 -2.2": ["remit"], "2.5 -0.7 -2.5": ["rambling"], "-0.1 3.0 7.8": ["mailings"], "7.8 9.9 2.1": ["steward"], "7.1 4.6 1.5": ["redevelop"], "10.8 15.8 5.5": ["particle"], "13.6 3.6 9.2": ["sans"], "0.6 0.7 1.9": ["uninjured"], "2.5 19.7 11.1": ["nationalists"], "-2.5 10.6 -1.4": ["degrade"], "-3.2 1.2 5.8": ["putback", "fibrates"], "5.8 5.4 6.5": ["impersonate"], "7.8 8.3 17.3": ["drizzle"], "-4.7 4.7 7.2": ["borderline"], "4.6 12.8 8.7": ["batons"], "-0.5 11.5 5.6": ["lifesaving"], "14.2 6.6 17.3": ["scraping"], "4.5 0.8 -0.6": ["gushed"], "2.9 11.2 2.1": ["eleventh"], "18.5 3.8 44.8": ["mushroom"], "7.2 28.1 7.2": ["blindly"], "2.9 8.6 3.3": ["inflamed"], "12.3 10.1 11.0": ["glee"], "-3.4 25.1 -3.5": ["sympathizers"], "10.0 4.5 11.8": ["vanity"], "1.5 16.2 15.7": ["faceoff"], "17.5 1.9 8.0": ["teetering"], "7.7 8.3 22.8": ["docking"], "1.7 -0.5 0.7": ["dosing"], "3.4 11.4 12.7": ["til"], "9.5 20.8 8.5": ["nightfall"], "14.7 6.2 -1.8": ["igniting"], "7.9 17.2 4.5": ["numerical"], "14.6 3.6 -5.1": ["transformational"], "-3.6 0.8 10.2": ["bungalow"], "-3.0 11.9 0.3": ["mustered"], "2.7 3.5 -2.6": ["exemplified"], "5.6 16.9 1.3": ["tormented"], "6.9 12.7 5.5": ["overarching"], "12.3 8.5 3.0": ["oasis"], "9.0 2.1 -3.8": ["fraudulently"], "1.4 11.1 0.2": ["elicit"], "-2.6 1.8 11.9": ["cigars"], "10.6 10.5 12.2": ["spoiling", "kanda"], "6.9 2.7 3.7": ["adapters"], "6.2 18.3 4.5": ["scheming"], "12.7 7.8 21.8": ["conservationists"], "5.4 12.1 7.3": ["blatantly"], "10.3 5.2 2.8": ["straightaway"], "5.0 8.4 1.1": ["trounced"], "-0.7 15.8 5.3": ["ballclub"], "14.1 6.9 8.0": ["amphitheater"], "12.3 5.2 14.2": ["stool"], "11.6 8.2 4.6": ["flips"], "2.2 6.0 5.0": ["abbreviated"], "-2.3 -1.4 12.2": ["cabaret"], "5.5 28.5 8.9": ["whomever"], "15.6 10.1 8.9": ["opaque"], "15.9 25.9 10.2": ["folly"], "-2.2 1.6 1.6": ["summaries"], "-3.1 4.3 8.6": ["superannuation"], "16.4 1.0 9.4": ["binge"], "9.0 2.9 7.3": ["legit"], "2.1 1.1 4.8": ["choirs"], "5.2 10.7 11.0": ["node"], "18.4 5.9 11.9": ["mosaic"], "-2.7 8.6 8.7": ["uncles"], "2.2 2.9 3.7": ["unclaimed"], "16.5 15.1 12.9": ["chests"], "8.3 14.2 4.8": ["counteract"], "2.6 7.1 35.0": ["veggies"], "-0.7 16.2 0.3": ["victors"], "-4.8 10.6 3.4": ["unreported"], "8.8 -4.5 -0.0": ["stationery"], "7.2 10.9 4.8": ["charting"], "13.1 3.5 3.4": ["placards"], "13.0 22.4 18.2": ["spammers"], "-9.1 2.7 5.8": ["appraisals"], "6.8 18.2 3.5": ["electrons"], "15.3 1.9 5.6": ["miscellaneous"], "1.9 16.0 2.0": ["distort"], "14.1 20.0 18.0": ["witch"], "11.2 21.7 8.0": ["skirmish"], "-3.2 0.7 5.2": ["cardholders"], "18.2 8.1 6.2": ["nervously"], "17.6 17.7 5.5": ["emblem"], "9.2 8.6 8.6": ["tutorial"], "13.8 4.8 8.5": ["selloff"], "9.5 3.0 6.4": ["housekeeper"], "17.8 22.6 9.7": ["imagining"], "10.0 -2.1 19.1": ["plum"], "11.1 6.3 10.1": ["strangling"], "0.9 8.0 2.6": ["forecaster"], "18.5 14.7 14.3": ["plank"], "15.8 8.4 20.1": ["rotting"], "-4.0 -0.9 2.0": ["tutors"], "10.2 -1.6 5.1": ["overpaid"], "6.1 6.5 0.6": ["sipping"], "16.1 -4.0 2.4": ["underwrite"], "13.1 18.9 35.3": ["squirrels"], "9.7 3.4 11.3": ["reared"], "23.0 3.8 17.0": ["mounds"], "1.6 10.4 5.1": ["jabs"], "-0.4 6.4 11.6": ["deference"], "-0.1 8.5 1.8": ["pardoned"], "2.0 10.3 1.5": ["instigated"], "1.0 16.5 9.3": ["elude"], "16.4 13.4 19.2": ["ray"], "0.8 10.4 6.9": ["antioxidants"], "10.1 4.4 3.9": ["trotted"], "12.1 0.3 6.2": ["materialized"], "8.3 7.0 -3.4": ["modernized"], "-1.3 1.5 1.6": ["translations"], "7.4 -3.8 5.1": ["retails"], "6.7 1.6 10.0": ["pare"], "5.5 2.8 2.9": ["foresees"], "3.7 2.2 11.5": ["perplexed"], "8.9 22.5 10.7": ["cliche"], "3.6 2.6 14.6": ["sweaters"], "11.3 4.4 26.0": ["stew"], "-0.6 6.0 32.0": ["harvests"], "4.1 5.6 5.7": ["augmented"], "-6.4 11.9 4.7": ["criterion"], "6.6 6.5 4.3": ["painstaking"], "4.0 3.9 7.6": ["kernel"], "-2.5 10.4 -0.0": ["synagogues"], "6.3 15.3 5.0": ["unreal"], "20.1 -3.2 7.9": ["fronted"], "3.5 9.1 27.4": ["grasses"], "10.2 2.2 3.2": ["experimented"], "0.7 6.3 8.5": ["outflow"], "8.5 31.7 7.6": ["defenseless"], "2.6 2.6 -3.5": ["coasted"], "4.6 8.6 2.1": ["resiliency"], "7.4 11.4 16.9": ["spreadsheet"], "1.0 6.7 34.7": ["snapper"], "19.2 4.5 8.7": ["cascade"], "4.0 7.1 3.7": ["censored"], "1.4 1.3 6.0": ["reused"], "-1.1 5.1 16.1": ["breeder"], "4.6 3.4 0.4": ["chronicle"], "27.8 9.4 5.7": ["skyscrapers"], "2.9 6.1 -3.8": ["befriended"], "6.9 10.9 2.0": ["pulpit"], "-8.2 2.8 2.2": ["commentaries"], "6.9 5.8 6.8": ["pooling", "designedto"], "3.9 9.4 13.9": ["karate"], "21.8 12.0 7.4": ["microscopic"], "34.6 21.2 27.4": ["spider"], "-7.3 3.1 7.4": ["correctional"], "7.8 9.7 8.6": ["contagion"], "7.1 0.9 -0.1": ["countrywide"], "1.6 0.5 16.0": ["hash"], "20.3 21.3 5.1": ["heavens"], "17.5 5.9 5.8": ["subcontractor"], "9.3 19.8 5.6": ["atrocious"], "-0.5 13.5 9.2": ["libertarian"], "2.5 4.8 -1.0": ["strenuous"], "5.6 6.6 3.4": ["uploading"], "1.9 8.4 0.4": ["pronouncements"], "3.3 13.4 10.2": ["haunts"], "3.8 6.9 5.5": ["font"], "4.7 10.0 9.1": ["linguistic"], "-5.8 5.9 -3.4": ["signatories"], "12.1 7.8 2.5": ["coincidentally"], "5.6 2.4 10.2": ["knitting"], "-0.0 23.9 7.5": ["belligerent"], "5.9 1.7 0.6": ["dispensed"], "12.8 7.3 10.7": ["shepherd"], "5.7 17.0 -2.4": ["audible"], "-2.6 3.2 2.3": ["workflows"], "2.0 23.5 3.2": ["abetting"], "-0.0 -6.3 -5.2": ["resonated"], "7.4 11.1 12.7": ["loonie"], "-3.3 -0.3 12.5": ["mammograms"], "8.6 1.9 2.2": ["queuing"], "18.9 10.3 14.0": ["bum"], "1.3 11.8 1.2": ["faithfully"], "11.3 10.3 6.7": ["pierced"], "2.2 16.1 -0.5": ["gunbattle"], "6.9 7.7 5.3": ["renders"], "19.2 8.9 8.8": ["hoist"], "1.5 6.5 2.0": ["migraine"], "9.4 7.0 7.2": ["clamor"], "1.9 23.1 12.5": ["liberalism"], "19.4 10.2 4.6": ["mysteriously"], "7.8 -2.0 9.9": ["titanium"], "1.1 7.9 -5.6": ["communicates"], "6.9 17.1 0.5": ["deceiving"], "3.2 9.9 7.0": ["telescopes"], "6.0 9.9 9.9": ["defies"], "11.2 15.7 14.8": ["imitation"], "7.8 17.6 1.8": ["adaptable"], "26.3 11.2 13.8": ["fabled"], "13.3 5.1 13.2": ["peeled"], "3.1 2.6 7.0": ["dishing"], "3.4 20.4 8.2": ["democrats"], "10.8 26.1 14.5": ["swords"], "15.5 14.9 11.9": ["motorized"], "2.7 8.1 1.6": ["reconstructed"], "8.7 15.0 13.8": ["starve"], "-0.6 -0.3 0.1": ["heartened"], "2.5 -1.7 17.7": ["mellow"], "-0.8 14.3 6.4": ["degraded"], "19.6 17.6 35.4": ["squirrel"], "11.3 27.0 4.0": ["deserts"], "14.4 19.7 14.0": ["crooks"], "0.2 2.3 4.5": ["roughing"], "20.4 16.5 10.6": ["cosmic"], "3.8 9.1 1.6": ["dissuade"], "21.0 4.3 7.6": ["dodgy"], "13.9 15.5 12.1": ["bulldozer"], "9.6 8.7 0.3": ["insolvent"], "7.7 14.6 13.5": ["goggles"], "7.1 12.0 13.3": ["monk"], "21.1 3.9 -1.2": ["plastered"], "-0.6 12.8 6.9": ["measles"], "4.1 7.6 3.4": ["bible"], "6.1 15.9 5.3": ["horseback"], "6.6 3.1 -4.0": ["dedicating"], "12.6 -1.3 9.3": ["topless"], "4.4 -0.8 2.1": ["fuming"], "3.2 4.2 -7.9": ["communique"], "4.0 7.5 25.4": ["pancakes"], "-4.0 1.2 30.5": ["entrees"], "-0.7 -9.4 8.7": ["renewals"], "16.2 7.8 6.6": ["techno"], "4.6 8.8 3.5": ["fancied"], "11.8 16.5 15.2": ["peasants"], "3.6 11.5 0.9": ["barricaded"], "-2.4 10.3 6.0": ["rebounder"], "3.4 13.4 2.0": ["adored"], "12.1 8.0 17.6": ["stacking"], "-8.9 5.1 1.8": ["rabbis"], "0.9 2.5 29.2": ["steaks"], "3.2 12.1 6.5": ["methodical"], "25.2 34.1 16.2": ["demon"], "20.1 -3.0 9.0": ["sweetened"], "1.5 7.7 15.3": ["viagra"], "6.0 16.2 7.7": ["boo"], "0.2 14.6 9.3": ["blinds"], "5.4 31.0 6.0": ["occupiers"], "1.7 5.9 1.8": ["debutant"], "-7.2 -0.8 5.4": ["recital"], "11.4 3.2 3.4": ["carted"], "2.0 7.0 16.2": ["dope"], "2.6 4.1 2.1": ["motorsport"], "12.9 -1.5 3.4": ["churned"], "-1.2 -0.8 16.6": ["cottages"], "2.3 12.0 11.8": ["ancestral"], "-2.1 9.2 1.7": ["referencing"], "10.1 12.1 8.4": ["pausing"], "13.6 1.3 0.9": ["verticals"], "-0.1 -0.4 1.0": ["inductees"], "6.4 6.0 0.9": ["snippets"], "13.7 11.1 15.8": ["crooked"], "-8.9 -3.3 10.3": ["workloads"], "0.5 4.1 7.3": ["escorts"], "8.8 15.2 19.0": ["tsunamis"], "3.9 7.5 6.8": ["automating"], "-1.8 13.2 1.5": ["closeness"], "4.8 2.8 -3.2": ["reaffirms"], "5.7 12.5 5.0": ["smartly"], "15.1 3.2 9.8": ["shenanigans"], "3.4 16.6 -4.3": ["wrongs"], "7.3 17.3 -0.0": ["grudge"], "-6.8 9.0 1.8": ["defection"], "-0.6 25.6 16.7": ["disciples"], "-1.5 16.3 1.6": ["disingenuous"], "4.5 8.7 2.6": ["corrective"], "9.3 11.8 22.6": ["lures"], "9.3 7.7 10.1": ["prairie"], "-0.2 2.7 6.2": ["paternity"], "-3.6 10.6 2.0": ["detaining"], "-1.2 7.4 9.9": ["lifeguard", "cefepime"], "4.6 0.5 24.8": ["kilo"], "2.6 21.5 2.7": ["heinous"], "-0.0 16.1 2.2": ["delusional"], "9.8 14.1 9.9": ["inhabit"], "-5.2 2.3 9.0": ["dismissals"], "17.5 7.0 4.2": ["humming"], "7.0 1.4 64.3": ["cod"], "21.4 9.6 27.1": ["crocodile"], "-3.0 7.2 3.9": ["remix"], "24.5 14.7 5.4": ["suitor"], "6.0 6.6 -1.1": ["manuals"], "-2.8 18.0 2.3": ["objectively"], "8.7 20.1 4.2": ["mystical"], "7.7 7.7 -2.8": ["woken"], "6.5 17.1 5.4": ["childish"], "-12.4 7.8 4.1": ["elaborated"], "15.2 10.4 26.9": ["chick"], "3.8 8.6 14.5": ["woodland"], "23.6 13.1 10.0": ["geeks"], "-2.3 7.5 11.8": ["kennel"], "7.9 6.3 16.4": ["oilsands"], "2.6 6.7 5.3": ["indexed"], "6.8 14.5 20.0": ["pucks"], "13.5 9.3 11.9": ["observatory"], "3.4 8.5 17.1": ["blooming"], "5.2 21.3 7.7": ["deceit"], "1.3 6.7 4.4": ["underfunded"], "4.5 5.6 6.6": ["receding"], "4.6 10.3 16.0": ["wardens"], "-3.5 4.5 -2.4": ["volunteerism"], "8.6 1.4 3.6": ["cleans"], "5.6 -2.6 8.8": ["rave"], "-0.6 39.0 3.4": ["traitor"], "1.0 13.5 6.6": ["legislate"], "2.6 25.2 8.7": ["inhuman"], "17.8 10.4 2.4": ["conspicuous"], "20.2 0.3 8.5": ["overpriced"], "10.8 10.7 12.8": ["jargon"], "-0.0 9.9 8.1": ["punting"], "4.4 18.5 -0.1": ["fragmentation"], "14.3 10.2 12.8": ["lumps"], "18.0 4.4 3.7": ["supermodel"], "6.3 14.5 13.9": ["pollen"], "8.8 2.1 -0.3": ["stitched"], "-1.4 -0.5 3.1": ["heeded"], "2.5 0.9 7.5": ["projectors"], "6.8 1.1 9.2": ["papal"], "10.1 9.6 42.4": ["broccoli"], "14.1 5.4 28.6": ["buoy"], "12.8 -2.2 4.9": ["cr"], "-0.7 16.7 8.6": ["unintentional"], "9.6 13.7 22.9": ["archipelago"], "12.8 8.9 12.3": ["bak"], "2.9 8.3 5.7": ["channeling"], "-0.1 14.5 1.1": ["overrated"], "-5.2 10.9 5.5": ["likable"], "-0.6 2.9 10.4": ["showbiz"], "9.4 12.4 -4.8": ["detector"], "9.5 6.3 4.8": ["numbering"], "7.8 3.8 -0.4": ["lags"], "8.5 6.4 7.7": ["hamlet"], "-0.5 -1.3 0.9": ["winningest"], "16.6 8.1 10.4": ["backstop"], "4.0 16.5 7.3": ["corrupted"], "8.9 -0.7 -0.4": ["racy"], "9.0 11.2 2.2": ["epitome"], "7.6 14.5 9.7": ["pedophile"], "14.9 -4.0 -7.3": ["nyse"], "11.0 9.0 5.5": ["teaser"], "6.3 17.0 2.8": ["recklessly"], "1.8 1.7 5.5": ["brothel"], "12.4 18.3 10.6": ["afar"], "3.7 31.8 7.0": ["civilizations"], "-3.0 8.3 -0.1": ["wayside"], "10.7 14.4 16.9": ["boulders", "bedstand"], "8.4 3.0 5.0": ["frills"], "4.0 -1.2 -1.9": ["consented"], "16.1 -0.8 1.8": ["downbeat"], "-1.8 -7.3 4.2": ["refunded"], "8.5 10.4 11.9": ["shatter"], "-1.8 14.1 0.3": ["untenable"], "12.8 9.1 9.7": ["bewildered"], "5.2 5.6 6.1": ["lofted"], "3.6 3.3 8.8": ["polo"], "3.8 13.0 0.3": ["mettle"], "9.6 0.5 27.9": ["boardwalk"], "-2.5 0.8 11.5": ["excursions"], "0.9 1.2 -2.1": ["structuring"], "4.2 4.5 12.7": ["idled"], "18.2 5.4 1.5": ["decliners"], "6.3 8.7 2.9": ["strolling"], "2.8 3.4 2.1": ["footnote"], "17.2 3.6 6.8": ["raking"], "6.0 0.8 7.6": ["offsets"], "2.5 2.1 -0.5": ["punted"], "-1.9 25.9 10.1": ["lieutenants"], "13.4 11.7 6.6": ["felled"], "3.2 12.6 7.5": ["bearings"], "2.5 1.9 7.1": ["boroughs"], "9.3 0.2 5.6": ["sewn"], "-4.3 1.7 7.6": ["pretrial"], "3.0 19.3 13.4": ["idols"], "1.2 1.8 2.1": ["provost"], "0.4 11.4 9.2": ["sportsman"], "7.6 14.2 14.5": ["sleet"], "-0.1 1.8 8.5": ["infertility"], "9.7 28.5 6.2": ["conquest"], "18.9 4.1 20.2": ["fluffy"], "20.7 2.8 9.6": ["wholesaler"], "0.0 12.1 3.2": ["reformers"], "-3.3 11.0 2.0": ["indict"], "5.5 6.0 1.3": ["outnumber"], "10.8 13.8 24.9": ["mating"], "9.6 2.1 1.0": ["outlay"], "12.1 17.6 14.3": ["darts"], "3.3 2.7 1.0": ["procured"], "0.5 11.8 13.2": ["biker"], "14.2 14.6 20.4": ["pigeons"], "14.0 0.3 9.1": ["softness"], "10.1 13.8 14.5": ["hut"], "-5.7 1.9 -0.7": ["fosters"], "-4.0 10.8 5.3": ["discord"], "12.7 2.9 9.1": ["restarting"], "2.7 6.4 1.1": ["closets"], "1.4 1.2 -0.7": ["precedence"], "20.7 0.0 33.3": ["spaghetti"], "9.9 15.7 0.6": ["rejoice"], "9.6 12.9 10.3": ["huh"], "-3.3 0.9 6.1": ["drier"], "-0.5 2.7 8.8": ["schoolers"], "6.1 3.2 15.8": ["zoos"], "13.7 6.5 3.3": ["erroneously"], "8.9 2.3 7.3": ["stiffer"], "20.8 -4.7 9.2": ["glitzy"], "11.1 3.1 6.3": ["chewed"], "-5.8 -1.1 1.1": ["disbursed"], "1.7 3.3 5.2": ["commenter"], "10.9 1.2 12.2": ["dole"], "20.6 21.5 4.9": ["archrival"], "-3.9 1.8 -0.9": ["gratified"], "19.0 5.9 9.2": ["triangular"], "12.1 12.4 1.2": ["buffs"], "3.0 6.1 16.5": ["skateboarding"], "-1.9 -0.8 8.4": ["stent"], "2.2 13.0 7.6": ["receptors"], "10.9 13.9 6.5": ["coffins"], "1.8 9.1 1.9": ["physiological"], "19.0 19.2 7.7": ["swarming"], "-1.7 10.3 2.0": ["tribunals"], "9.9 8.2 5.2": ["locomotive"], "0.4 15.9 -3.3": ["distortions"], "2.9 16.1 0.1": ["complicit"], "1.8 6.4 3.9": ["benchmarking"], "5.0 5.5 3.1": ["forgettable"], "-3.2 4.3 10.6": ["acupuncture"], "-9.4 6.6 3.0": ["dialogues"], "15.8 16.7 2.2": ["unlocking"], "10.3 10.6 12.1": ["volcanic"], "-1.3 12.4 7.0": ["panicking", "infirmed"], "7.0 12.3 2.0": ["periphery"], "7.7 13.5 -0.4": ["inconceivable"], "12.0 25.9 0.9": ["renegade"], "9.2 9.8 9.9": ["faking"], "2.8 14.3 5.6": ["uncharacteristic"], "-2.3 7.6 6.5": ["sprinklers"], "22.2 8.1 17.6": ["wobbly"], "4.3 16.4 6.1": ["sender"], "1.5 2.2 22.1": ["drywall"], "8.8 10.1 4.4": ["dazed"], "8.3 5.4 5.3": ["heighten"], "1.4 -4.6 22.7": ["breakfasts"], "0.8 17.1 7.0": ["unbalanced"], "0.9 4.9 14.1": ["racetracks"], "-5.8 7.5 5.1": ["trey"], "1.4 12.9 32.1": ["reds"], "15.9 13.0 8.8": ["shrinks"], "15.3 13.5 5.7": ["lashing"], "1.5 4.1 6.1": ["ss"], "11.1 8.7 5.5": ["blockbusters"], "6.1 25.9 4.6": ["suppressing"], "17.3 9.0 10.2": ["skeletons"], "2.8 -0.7 12.9": ["dined"], "-0.3 10.5 -0.1": ["fatigued"], "-0.6 10.8 0.2": ["wholeheartedly"], "14.4 9.8 10.9": ["flimsy"], "-3.1 4.4 7.3": ["interpreters"], "13.8 6.4 28.8": ["seabed"], "8.9 11.8 17.9": ["apron"], "6.2 6.7 4.4": ["stoned"], "12.1 19.8 9.6": ["cloak"], "12.5 9.3 2.8": ["gen"], "1.8 10.4 10.3": ["potency"], "-1.5 20.5 4.7": ["inexcusable"], "-3.1 7.2 10.7": ["laments"], "-2.9 3.4 5.5": ["adhered"], "0.7 9.9 3.1": ["doubting"], "-0.1 7.9 3.5": ["mediums"], "-0.4 -3.1 6.6": ["syringes"], "5.0 0.4 8.4": ["wane"], "10.4 0.6 5.5": ["reusable"], "4.2 4.5 -4.5": ["embody"], "-0.5 5.6 0.9": ["teed"], "9.2 14.5 10.4": ["sap"], "19.4 11.3 0.7": ["inventing"], "0.3 5.6 7.6": ["lingers"], "5.9 10.1 16.4": ["hops"], "2.6 12.7 4.6": ["saints"], "4.0 6.8 1.5": ["overjoyed"], "8.5 22.3 4.6": ["blockers"], "-0.9 4.3 7.3": ["minibus"], "-6.7 3.0 -0.6": ["resided"], "9.4 13.8 7.5": ["inexplicable"], "-0.8 -0.3 -5.3": ["disqualify"], "9.7 -3.1 3.7": ["heeled"], "0.0 9.5 8.7": ["hazing"], "7.6 5.3 22.9": ["sock"], "2.3 8.1 2.1": ["evaded"], "17.8 10.6 0.9": ["harnessing"], "11.2 20.7 19.2": ["parasites"], "-3.9 6.9 1.3": ["propositions"], "1.1 8.1 6.8": ["conformity"], "6.8 14.1 6.4": ["stains"], "11.6 4.2 9.7": ["afoot"], "-1.1 -0.7 2.5": ["restores"], "2.8 2.8 7.0": ["stroked"], "3.7 6.2 4.9": ["evaporate"], "10.1 2.9 7.6": ["brighten"], "1.2 8.0 -0.4": ["stead"], "3.6 6.5 7.4": ["lessened"], "12.6 12.2 10.9": ["alas"], "5.9 20.7 6.2": ["invasions"], "9.3 2.4 1.9": ["bordered"], "-1.9 -3.2 1.0": ["chairing"], "8.3 2.4 7.2": ["marveled"], "1.1 10.3 2.0": ["conveying"], "1.2 9.6 9.4": ["unknowns"], "5.9 9.2 8.8": ["anxieties"], "8.6 11.0 -1.1": ["workhorse"], "0.1 10.5 6.4": ["sugars"], "-3.1 6.8 6.6": ["incest"], "10.3 10.5 20.1": ["freighter"], "17.8 1.7 6.3": ["onetime"], "-1.7 16.9 0.8": ["eyewitnesses"], "4.9 8.6 9.0": ["slant", "nongovernment"], "0.4 7.2 6.8": ["ninety"], "19.1 8.6 22.2": ["swells"], "11.0 16.4 8.5": ["conundrum"], "8.8 21.9 5.1": ["evading"], "4.3 5.1 6.2": ["tremor", "gosselin"], "1.4 17.6 14.5": ["dogfighting"], "0.3 6.8 6.5": ["spambots"], "9.7 10.9 6.3": ["mute"], "-1.1 8.6 5.0": ["debatable"], "5.1 9.8 6.2": ["reverted", "unfinanced"], "17.0 1.6 8.4": ["pc"], "-1.7 8.6 2.2": ["tarnish"], "4.1 6.3 -5.0": ["monetize"], "11.5 10.0 1.7": ["smelling"], "-2.8 14.1 5.5": ["stances"], "-1.1 6.5 21.7": ["allowable"], "0.7 0.2 23.0": ["composting"], "6.1 9.2 -1.5": ["clapped"], "4.4 13.1 13.9": ["firehouse"], "13.2 8.1 14.0": ["dwellers"], "1.5 4.9 0.4": ["binds"], "0.9 17.2 9.8": ["elitist"], "6.1 28.9 -8.1": ["liberating"], "13.5 15.6 13.5": ["comet"], "1.8 7.2 4.8": ["tweeting"], "17.2 2.0 13.2": ["cheeky"], "9.8 -1.6 2.1": ["standardize"], "1.8 10.1 12.4": ["shopkeepers"], "5.4 2.3 4.8": ["falsified"], "1.1 6.7 5.7": ["sorority"], "5.8 13.2 10.4": ["proportionate"], "2.9 22.5 3.2": ["atheist"], "4.4 -4.0 3.7": ["waiving"], "0.5 1.7 -4.5": ["reiterates"], "-2.0 4.9 1.9": ["continuum"], "-0.2 12.3 10.3": ["predicated"], "12.3 12.1 12.9": ["oft"], "-6.8 12.4 -0.1": ["distinctions"], "13.0 26.4 5.6": ["hating"], "-6.4 6.4 -1.0": ["counseled"], "6.3 4.1 17.3": ["hardwood"], "-1.5 3.0 1.5": ["emigrated"], "4.5 11.4 3.0": ["payer"], "11.2 13.9 29.3": ["lighthouse"], "15.0 2.5 9.3": ["parted"], "8.1 5.2 36.6": ["curry"], "19.9 10.9 12.7": ["ladders"], "2.7 16.9 5.4": ["eavesdropping"], "13.6 8.9 10.7": ["industrialization"], "2.0 7.2 0.4": ["diligence"], "3.9 3.1 6.2": ["reprise"], "10.9 -1.6 10.5": ["snared"], "2.2 8.3 12.5": ["melancholy"], "5.8 4.0 1.3": ["backseat"], "1.6 6.8 1.9": ["designating"], "7.1 15.4 17.6": ["sow"], "14.9 7.5 8.0": ["peering"], "16.4 22.3 8.5": ["mindless"], "2.9 -1.7 6.2": ["workstation"], "3.9 12.1 8.6": ["undeniably"], "14.9 7.1 19.1": ["chopping"], "-4.4 8.6 -1.9": ["combustion"], "1.0 10.3 3.4": ["minimizes"], "1.2 4.4 5.5": ["plying", "photovoltaics"], "0.6 14.8 3.6": ["debtors"], "-3.0 -0.3 -1.8": ["inquiring"], "8.8 17.5 17.4": ["cliffs"], "2.3 3.9 -2.2": ["implored"], "0.1 13.7 2.1": ["externally"], "1.8 7.4 -8.8": ["congratulating"], "-1.5 2.4 -5.0": ["outbursts"], "7.3 9.1 20.1": ["bulb"], "16.8 6.6 1.1": ["pelted"], "-0.6 5.5 4.9": ["spinal"], "-3.0 10.1 8.3": ["biopsy"], "5.8 21.6 9.3": ["bystander"], "2.4 5.7 -2.4": ["accretive"], "9.0 18.9 14.6": ["macho"], "16.6 -4.3 0.9": ["herald"], "4.2 9.6 17.8": ["yeast"], "16.2 13.9 2.8": ["ingenious"], "6.8 8.0 18.0": ["feces"], "-0.3 7.7 0.6": ["recurrent"], "8.6 14.2 16.0": ["sands"], "15.6 5.6 7.7": ["agribusiness"], "14.8 11.2 4.5": ["scaring"], "6.9 13.9 -0.1": ["uncovering"], "16.3 11.1 9.6": ["skulls"], "17.1 5.1 10.2": ["crumpled"], "6.1 3.6 6.0": ["confluence"], "1.0 5.8 1.5": ["ledger"], "18.0 11.2 10.4": ["spooky"], "-5.2 7.7 -1.1": ["disregarded"], "0.0 8.0 7.6": ["frontcourt"], "9.7 6.1 20.2": ["cull"], "11.4 5.1 16.2": ["resin"], "-7.3 5.5 14.9": ["morphine"], "2.0 4.5 3.5": ["rework"], "13.0 2.0 -0.6": ["preeminent"], "1.7 8.8 10.1": ["drawers"], "2.9 4.7 4.5": ["leery"], "10.6 8.5 5.4": ["baffling", "afflicting"], "8.8 1.6 -2.8": ["lambasted"], "5.6 0.1 5.7": ["offing"], "7.5 7.9 9.7": ["wrinkle"], "-8.9 1.1 -2.7": ["interdisciplinary"], "2.3 5.9 45.5": ["asparagus"], "8.6 20.1 9.6": ["obstruct"], "5.9 9.2 12.8": ["relics"], "4.0 9.8 27.5": ["kiwi"], "5.9 -1.9 3.7": ["centennial"], "10.6 17.7 -0.2": ["shielding"], "3.8 7.4 4.8": ["lashes"], "13.3 9.5 18.8": ["muck"], "6.3 1.5 27.9": ["deepwater"], "7.1 17.1 3.2": ["undoing"], "10.0 -2.1 3.9": ["inserts"], "6.8 6.1 -1.5": ["enamored"], "1.8 6.3 6.7": ["nip"], "5.5 11.2 12.9": ["soot"], "4.7 -1.2 -6.0": ["championing"], "-0.2 9.8 14.3": ["welterweight"], "0.1 3.6 8.4": ["solicitations"], "10.0 8.1 4.3": ["journeyman"], "2.4 13.4 6.0": ["sensitivities"], "-2.2 17.2 13.8": ["settler"], "9.6 8.7 9.3": ["rationalization"], "8.6 -2.9 1.3": ["panned"], "8.7 4.0 1.4": ["stoke"], "8.3 1.5 12.6": ["padding"], "12.3 4.7 5.7": ["unfazed"], "7.6 2.6 6.5": ["toughen"], "6.8 5.0 5.4": ["straighten"], "6.6 11.4 14.6": ["incidental"], "0.5 17.1 1.2": ["willful"], "7.5 1.6 32.1": ["pudding"], "5.6 11.6 11.2": ["gutter"], "12.2 11.5 8.9": ["freaking"], "4.6 12.2 -0.5": ["embed"], "3.3 31.5 0.5": ["hideout"], "11.1 19.8 11.1": ["unnatural"], "-7.4 6.1 1.8": ["impart"], "2.5 6.4 5.5": ["commensurate"], "6.0 -2.0 14.1": ["dishwasher", "manse"], "-7.8 6.3 2.6": ["conscientious"], "7.0 11.7 12.4": ["expertly"], "17.2 25.6 10.6": ["compass"], "2.4 2.8 -0.7": ["saloon"], "4.7 11.1 9.1": ["vividly"], "13.4 23.3 6.3": ["vile"], "0.2 16.8 8.9": ["wills"], "13.7 7.1 7.5": ["fountains"], "0.6 8.3 -0.2": ["politicized"], "12.2 11.0 4.8": ["salespeople"], "10.5 2.5 6.5": ["multiples"], "14.7 5.1 2.4": ["bundling"], "-2.6 1.4 0.4": ["elapsed"], "6.2 6.2 14.8": ["swimsuit"], "11.9 11.1 4.9": ["preposterous"], "-4.6 7.0 -2.9": ["conveys"], "-2.7 7.2 1.4": ["rehabilitating"], "-2.4 8.3 9.2": ["crosswalk"], "7.4 4.1 11.5": ["wade"], "30.1 2.0 12.0": ["neon"], "7.4 5.3 7.9": ["harmonious"], "7.9 4.8 -2.8": ["trashed"], "0.2 13.9 9.5": ["moods"], "18.4 6.0 5.4": ["fad"], "1.9 2.2 1.5": ["searchable"], "0.7 7.2 7.7": ["confesses"], "-0.5 3.5 6.4": ["headliner"], "6.8 16.2 5.0": ["inefficiency"], "2.4 3.8 7.6": ["franchising"], "4.6 -3.2 8.2": ["syringe"], "11.7 -0.8 2.6": ["clampdown"], "4.9 2.9 -3.6": ["refurbish"], "6.8 5.3 0.5": ["masterminded"], "-1.0 10.4 13.1": ["depletion"], "6.7 9.3 1.9": ["amassing"], "-3.6 9.6 -1.5": ["recuperating"], "3.1 -0.9 -0.3": ["elicited"], "7.4 8.3 7.0": ["transformer"], "7.8 14.4 8.1": ["eagerness"], "-3.2 1.0 -3.6": ["detract"], "-2.2 1.6 3.5": ["biopic"], "2.3 3.1 9.2": ["conservatively"], "-5.3 15.1 1.0": ["candor"], "-6.9 7.3 1.4": ["ventilator"], "-3.5 8.1 6.2": ["prioritized"], "13.4 9.4 1.4": ["roamed"], "0.3 7.4 11.6": ["governorship"], "0.0 12.4 11.2": ["equilibrium"], "1.6 7.1 -1.2": ["chastised"], "11.1 21.6 15.9": ["lick"], "10.0 2.2 9.0": ["fifths"], "3.2 12.0 4.3": ["dictating"], "-1.8 1.7 4.4": ["correlated"], "-7.8 27.4 -3.2": ["martyrdom"], "6.8 0.2 7.4": ["reais"], "6.9 15.2 28.6": ["coyote"], "7.6 5.2 -2.1": ["saturation"], "-0.2 -1.5 4.7": ["encoding"], "-2.5 0.6 -0.4": ["tabbed"], "7.2 6.7 21.7": ["china"], "11.8 -1.5 14.2": ["tinged"], "10.9 1.6 8.1": ["upping"], "-8.7 7.9 21.7": ["firewood"], "11.2 2.1 1.8": ["underperformed"], "-3.7 4.7 2.5": ["accrue"], "-1.3 3.6 0.1": ["curricula"], "-6.9 9.4 -5.5": ["disseminated"], "-4.4 8.1 0.9": ["disrepair"], "-4.0 13.7 8.4": ["mineralized"], "11.5 3.9 5.3": ["foreman"], "3.0 14.3 3.4": ["pointedly"], "-3.3 27.8 -0.8": ["subversive"], "4.9 5.0 -1.8": ["drugged"], "-0.0 8.8 10.6": ["wheelers"], "3.3 10.6 3.8": ["heaters"], "11.6 5.6 5.5": ["digits"], "3.8 13.9 5.2": ["meanings"], "4.9 -0.5 4.3": ["lakhs"], "2.5 5.7 3.2": ["diaspora"], "6.1 14.2 32.3": ["marsh"], "11.9 10.8 11.2": ["delisting"], "0.7 0.9 8.8": ["comp"], "10.8 7.9 7.8": ["whiff"], "5.0 9.9 10.2": ["campsite"], "-1.9 7.2 5.0": ["emailing"], "-2.4 1.3 4.6": ["sedans"], "-2.5 -3.9 0.6": ["reschedule"], "3.6 7.1 -0.4": ["briefcase"], "7.9 5.8 24.2": ["islanders"], "7.3 23.1 14.1": ["onscreen"], "2.0 -2.1 7.0": ["penciled"], "3.5 8.1 10.7": ["antivirus"], "3.4 9.4 10.2": ["knockouts"], "7.0 1.3 13.7": ["oversupply"], "5.2 14.4 5.5": ["reciprocal"], "5.1 9.4 9.7": ["congregate"], "-1.2 1.3 7.3": ["calmer"], "3.2 4.2 7.8": ["hourlong"], "13.4 28.3 6.6": ["protector"], "6.4 9.1 4.8": ["vents"], "-0.9 17.9 6.3": ["reinforcement"], "-1.4 -2.0 9.5": ["steers"], "-8.0 -2.6 4.9": ["officiated"], "7.5 10.5 11.8": ["housemates"], "10.5 4.9 24.7": ["platter"], "5.6 9.6 2.8": ["whitewash"], "5.5 2.1 -1.3": ["para"], "-1.8 28.3 7.9": ["retaliatory"], "7.2 1.3 8.0": ["opts"], "9.6 8.5 5.8": ["converging"], "0.5 -2.0 9.0": ["housekeeping"], "-7.0 2.9 5.3": ["hospitalizations"], "-3.1 12.4 2.8": ["misinterpreted"], "10.2 2.3 13.6": ["haired"], "-8.7 8.2 -1.0": ["liens"], "14.0 6.0 4.8": ["railed"], "3.8 -0.3 -1.8": ["sifting"], "8.9 17.9 20.3": ["lifeboat"], "6.0 -3.0 4.9": ["suitcases"], "2.5 0.7 12.7": ["smelter"], "10.9 1.2 3.5": ["accords"], "-8.1 6.0 0.6": ["catheter"], "0.4 10.7 10.0": ["worsens"], "-6.9 -0.4 13.9": ["allotments"], "10.8 6.1 8.5": ["tempt"], "9.2 9.9 8.5": ["transatlantic"], "8.1 12.8 5.5": ["seductive"], "-1.6 6.7 3.4": ["seventeen"], "13.6 8.4 19.5": ["shack"], "8.6 4.4 8.8": ["skit"], "0.4 9.8 -5.4": ["maximizes"], "4.4 9.0 3.9": ["chord"], "19.4 8.1 6.0": ["grids"], "11.3 12.2 7.7": ["lifeblood"], "8.7 18.1 3.1": ["doubters"], "5.0 8.5 8.2": ["adaptations"], "18.0 0.4 5.2": ["clogging"], "-6.3 33.4 8.4": ["counterinsurgency"], "-1.8 18.0 -0.9": ["incite"], "14.0 5.3 -4.2": ["restate"], "9.4 8.5 10.7": ["blanketed"], "-1.6 5.8 1.2": ["burglarized"], "-0.9 34.7 1.9": ["patriot"], "6.6 18.9 9.0": ["encroachment"], "14.5 11.0 -1.1": ["beheading"], "34.0 5.6 8.6": ["veritable"], "18.1 8.4 7.0": ["refiner"], "18.3 10.0 29.3": ["donut"], "7.3 10.9 6.3": ["conceivably"], "1.1 11.0 18.6": ["wreath"], "10.2 4.6 2.7": ["spewed"], "-3.0 12.3 -1.5": ["baptized"], "17.3 9.6 11.8": ["entangled"], "9.9 2.1 3.3": ["cementing"], "-0.3 9.1 41.5": ["freshwater"], "12.5 1.6 -2.7": ["testers"], "6.1 4.2 8.6": ["maroon"], "4.0 6.8 1.7": ["rewriting"], "0.0 4.3 8.9": ["fresher"], "7.1 -1.9 -0.1": ["businesswoman"], "12.4 13.1 4.9": ["incessant"], "15.4 12.8 1.5": ["limitless"], "2.4 -1.7 1.4": ["abnormalities"], "3.2 6.0 -2.3": ["resonance"], "19.6 5.7 11.6": ["burly"], "-6.1 6.3 9.7": ["solos", "invitationals"], "5.4 14.8 3.9": ["unconscionable"], "16.5 9.4 12.4": ["folklore"], "-1.7 13.0 2.7": ["advisable"], "-5.0 6.6 13.0": ["skied"], "13.0 5.1 0.0": ["wracked"], "3.3 9.8 12.8": ["uniformly"], "7.8 7.5 8.3": ["compensating"], "11.7 11.8 3.6": ["noose"], "-4.2 10.4 1.1": ["privy"], "3.1 1.8 15.7": ["herbal"], "18.8 25.7 9.8": ["lord"], "8.7 5.4 11.6": ["boomers"], "16.9 3.2 12.1": ["flopped"], "1.5 14.5 -0.4": ["enlisting"], "-9.0 7.8 5.5": ["equalize"], "3.1 13.0 6.2": ["inefficiencies"], "3.4 9.9 -1.8": ["speculations"], "15.2 21.3 21.6": ["rays"], "8.2 9.4 8.3": ["microprocessor"], "6.8 8.5 11.2": ["deft"], "3.9 9.9 4.3": ["optics"], "4.3 15.2 6.3": ["unofficially"], "17.8 2.1 -6.2": ["evangelist"], "7.1 11.5 2.7": ["ditches"], "7.2 5.7 8.1": ["subside"], "-10.3 11.6 1.5": ["recited"], "22.1 -0.3 15.1": ["swirl"], "0.2 -1.1 9.5": ["motels"], "8.7 12.8 4.8": ["genitals"], "15.7 2.3 -0.9": ["divestment"], "6.1 8.1 2.9": ["seventy"], "8.7 16.2 12.5": ["acrobatic"], "7.4 11.1 3.8": ["chills"], "9.1 6.5 6.5": ["convoluted"], "-2.0 20.4 4.8": ["disarming"], "-0.1 10.6 2.6": ["evict"], "13.8 -1.7 7.9": ["upended"], "8.2 9.6 7.9": ["blocs"], "7.6 23.2 7.5": ["thug"], "11.1 8.8 7.8": ["shoring"], "5.9 1.6 13.0": ["shingles"], "1.7 10.8 6.7": ["receptor"], "2.5 3.0 4.5": ["abolishing"], "7.2 5.9 10.1": ["comb"], "-5.2 17.8 7.7": ["obedience"], "1.8 18.1 6.7": ["skirmishes"], "9.7 -6.2 -2.5": ["paves"], "1.8 17.6 9.7": ["reverence"], "-2.4 4.9 17.2": ["swims"], "8.7 0.0 2.6": ["outpace"], "1.1 14.7 11.7": ["bipartisanship"], "14.0 0.7 10.7": ["handout"], "8.4 9.7 7.5": ["straps"], "13.0 -3.6 -0.8": ["tripling"], "-3.2 3.4 13.2": ["molybdenum"], "20.9 13.8 23.3": ["furry"], "-4.4 17.7 -2.1": ["incitement"], "2.9 5.7 9.1": ["robe"], "-1.0 5.2 8.9": ["ballads"], "11.3 -0.3 8.7": ["bubbling"], "-1.9 5.4 3.7": ["newsstands"], "3.4 1.5 17.2": ["fab"], "-3.4 7.1 3.1": ["amplifier"], "9.4 14.8 12.1": ["helper"], "-2.5 11.4 1.7": ["courteous"], "5.9 12.9 9.4": ["stinks"], "7.5 8.6 11.4": ["pours"], "9.8 2.7 8.4": ["lethargic"], "15.2 -3.6 15.5": ["scaffolding"], "0.4 0.3 3.8": ["necessitated"], "0.2 11.5 6.0": ["unseeded"], "0.4 -1.7 9.0": ["yearbook"], "10.0 15.0 4.0": ["stalked"], "-6.7 13.4 8.8": ["uncontested"], "7.9 4.8 5.9": ["minimalist"], "13.2 1.5 0.8": ["rumbled"], "-5.1 4.5 8.2": ["wicketkeeper"], "4.0 6.6 17.2": ["thinning"], "-4.7 12.9 0.8": ["recite"], "6.9 12.2 8.0": ["travesty"], "-11.9 9.0 2.1": ["dissenting"], "3.3 4.8 6.2": ["negated"], "9.9 1.3 1.3": ["enterprising"], "7.4 11.4 5.4": ["warms"], "18.2 7.4 8.6": ["steepest"], "3.7 14.3 17.6": ["rut"], "4.1 1.7 -4.0": ["centrally"], "9.7 5.7 4.8": ["trappings"], "-1.1 1.8 0.6": ["irked"], "5.1 -1.1 2.9": ["custodians"], "1.5 13.0 9.8": ["discharges"], "11.4 12.8 8.7": ["stingy"], "8.4 0.0 -0.2": ["tampered"], "5.7 9.8 4.2": ["fervent"], "-5.0 6.8 8.3": ["homestead"], "-2.7 6.5 2.8": ["defections"], "5.5 14.0 2.5": ["identifiable"], "4.6 1.2 7.4": ["rethinking"], "9.7 6.7 6.6": ["grandeur"], "4.8 10.1 7.8": ["downpour"], "-3.7 16.0 2.6": ["thinker"], "17.0 6.0 7.5": ["readied"], "-4.4 5.7 1.4": ["demotion"], "-0.3 6.4 12.2": ["lbw"], "17.3 8.3 15.9": ["grocer"], "13.8 8.2 13.8": ["sling"], "12.5 9.3 15.3": ["littering"], "-2.1 7.2 11.6": ["devolution"], "18.2 3.6 8.2": ["deflated"], "8.2 8.3 -2.3": ["unrealized"], "13.2 15.3 9.5": ["crafty"], "0.3 20.2 3.4": ["hindrance"], "-10.5 6.0 8.1": ["returnees"], "-4.7 10.6 7.7": ["repatriated"], "10.5 10.3 2.1": ["displace"], "2.3 12.0 4.5": ["sparing"], "4.2 6.7 2.6": ["linkage"], "0.5 -0.6 2.9": ["amp"], "3.0 -3.3 4.3": ["forego"], "5.7 2.5 -2.4": ["pamphlets"], "2.4 3.6 3.9": ["comebacks"], "1.8 24.2 13.2": ["wits"], "5.1 1.7 0.9": ["sift"], "-0.2 -3.4 5.2": ["satisfies"], "-7.2 23.7 9.4": ["subordinates"], "8.8 1.1 -7.4": ["commercializing"], "-1.6 14.7 21.9": ["poppy"], "-1.1 4.1 8.2": ["insertion"], "11.6 3.3 15.3": ["makings"], "15.9 5.2 7.0": ["lanky"], "-0.0 5.4 -6.7": ["condolence"], "3.5 8.8 19.0": ["rainwater"], "16.2 4.1 12.3": ["weighting"], "6.5 16.3 16.8": ["toxin"], "5.7 8.1 19.1": ["bottoms"], "2.6 -0.5 8.4": ["limo"], "11.3 3.2 14.0": ["roller"], "-4.0 21.7 6.7": ["motivator"], "19.4 11.8 30.0": ["sponge"], "7.0 11.7 1.5": ["flyover"], "14.1 2.3 7.8": ["kronor"], "13.1 0.4 2.0": ["clog"], "0.8 7.2 9.1": ["joblessness"], "0.3 4.1 0.5": ["modalities"], "-2.8 2.2 15.1": ["reruns"], "10.9 3.3 0.1": ["underlining"], "17.8 5.1 3.1": ["buggy"], "3.4 15.4 5.3": ["untouchable"], "8.1 -2.1 12.7": ["preschoolers"], "7.7 11.6 -0.3": ["nexus"], "22.3 1.9 5.2": ["replete"], "13.7 15.0 7.4": ["caricature"], "2.2 19.1 12.0": ["ism"], "-4.7 10.5 1.8": ["objectivity"], "-2.8 18.5 6.2": ["undemocratic"], "4.0 14.9 2.7": ["odors"], "-0.4 2.7 1.0": ["photovoltaic"], "3.7 19.9 5.2": ["antidote"], "-2.2 19.4 5.5": ["flashbacks"], "-3.7 5.3 5.8": ["predictability"], "15.7 6.6 0.7": ["bashed"], "3.7 4.7 2.0": ["admin"], "12.2 2.8 1.9": ["mauled"], "10.2 0.1 1.9": ["resolves"], "2.3 8.5 2.4": ["dismissive"], "7.8 -9.0 7.9": ["defray"], "35.6 8.6 3.4": ["conglomerates"], "1.8 6.9 0.9": ["vindication"], "-2.4 -2.4 12.3": ["indigent"], "14.6 7.0 -5.9": ["transformative"], "13.8 -0.5 16.9": ["raffles"], "3.6 5.9 -6.4": ["purport"], "26.8 29.3 12.3": ["fearsome"], "4.4 21.1 5.8": ["playable"], "9.9 11.1 2.1": ["vibrations"], "9.4 9.7 13.6": ["pennant"], "21.8 -6.8 2.2": ["swirled"], "10.0 13.5 9.4": ["therein"], "6.6 1.5 14.0": ["partake"], "5.2 4.9 17.8": ["lemonade"], "14.8 8.1 5.7": ["stumbles"], "5.6 6.7 0.5": ["ringtones"], "3.8 7.7 -0.1": ["inhaled"], "4.2 1.2 2.0": ["disputing"], "10.8 6.5 1.9": ["cluttered"], "-3.5 28.3 4.6": ["disarmed"], "1.6 3.2 11.7": ["dioceses"], "8.8 -1.2 -0.6": ["retracted"], "-3.7 14.3 9.4": ["sarcastic"], "1.2 4.6 1.9": ["adoptive"], "2.3 5.7 -0.6": ["calibration"], "8.7 7.0 35.9": ["steamed"], "1.8 8.4 32.0": ["herb"], "3.7 3.0 2.5": ["specifies"], "9.9 9.5 -0.1": ["thumped"], "10.7 0.2 6.0": ["smattering"], "12.6 5.3 1.4": ["profiting"], "8.5 8.4 10.2": ["gal"], "3.9 0.2 4.8": ["mingled"], "20.3 1.5 27.7": ["fiberglass"], "9.5 -2.5 1.1": ["receivership"], "2.7 7.5 8.3": ["compute"], "6.4 11.0 6.8": ["alderman"], "12.0 11.5 3.7": ["eyesore"], "8.6 0.8 -4.2": ["bulletins"], "6.1 8.3 9.8": ["additive"], "12.4 33.0 2.5": ["invincible"], "17.1 3.0 -5.0": ["divestiture"], "3.8 7.2 10.4": ["chuckled"], "5.9 11.7 9.6": ["deftly"], "1.5 5.4 1.6": ["upto"], "-6.2 2.6 3.1": ["convening"], "17.0 2.7 8.2": ["midmorning"], "4.9 1.8 0.4": ["reworked"], "7.3 23.6 4.0": ["armory"], "1.2 6.7 4.9": ["lineage"], "12.0 13.0 8.1": ["imitate"], "1.2 9.3 9.0": ["normalized"], "12.6 -2.1 2.4": ["bespoke"], "6.8 15.0 12.2": ["backdoor"], "-4.8 -0.4 8.4": ["enrollments"], "42.9 -3.0 -3.8": ["magnate"], "0.0 0.6 0.7": ["jr"], "2.6 7.1 8.0": ["touchline"], "10.4 13.9 9.1": ["devising"], "5.3 6.5 11.0": ["bleach"], "7.7 12.5 11.8": ["comers"], "14.4 3.6 -4.9": ["rename"], "12.3 8.3 9.7": ["amazement"], "6.8 3.2 6.0": ["organically"], "15.3 -0.8 11.1": ["coolers"], "-0.8 1.8 8.5": ["duplicated"], "6.7 13.4 5.3": ["activating"], "19.7 13.5 9.5": ["vertically"], "-7.6 6.2 0.2": ["nonfiction"], "6.7 7.1 6.9": ["tranquil"], "11.9 13.7 4.1": ["fling"], "21.0 -5.0 1.8": ["mulls"], "-4.3 9.0 -2.9": ["purview"], "-3.6 10.4 7.6": ["narration"], "13.8 7.2 20.2": ["sage"], "2.4 6.8 6.3": ["contrived"], "-0.1 5.0 4.9": ["craftsmanship"], "10.8 15.8 4.5": ["incomprehensible"], "5.1 14.8 -2.1": ["statesman"], "2.1 -1.8 -1.8": ["impressing"], "-0.2 6.4 1.9": ["barrister"], "13.5 8.4 18.3": ["sliver"], "4.0 1.3 8.9": ["grooves"], "6.8 -3.6 10.5": ["wigs"], "0.4 17.4 -2.7": ["injustices"], "6.3 10.1 5.8": ["crux"], "16.0 -1.3 2.6": ["starlet"], "4.2 5.4 9.8": ["archaeologist", "zoology"], "2.3 12.2 0.5": ["aloud"], "9.4 6.7 7.2": ["aching"], "-7.1 4.5 6.1": ["commutes"], "3.3 5.3 2.6": ["cribs"], "15.5 5.8 7.9": ["schoolgirl"], "13.2 7.3 -0.2": ["outdone"], "12.8 11.0 12.2": ["grasping"], "-1.7 2.9 7.0": ["referendums"], "10.9 25.4 20.8": ["torpedo"], "8.1 14.4 9.0": ["perverse", "aq"], "2.0 6.8 1.7": ["alot"], "10.3 1.8 9.5": ["trans"], "-0.7 17.0 7.3": ["playmakers"], "7.9 8.5 10.6": ["idyllic"], "-4.1 -5.2 -0.9": ["auditioned"], "0.4 6.9 -0.5": ["lithium"], "14.1 -0.2 4.7": ["cloned"], "0.9 6.9 7.5": ["dysfunction"], "-2.7 7.2 4.6": ["mitigated"], "9.4 10.7 25.0": ["tidal"], "12.8 9.7 -1.9": ["bombshell"], "5.2 13.1 1.7": ["democratization"], "1.2 13.1 0.1": ["escorting"], "2.0 1.5 0.9": ["stroller"], "12.4 7.9 9.7": ["gracefully"], "7.7 10.8 18.6": ["hardy"], "-10.4 5.7 3.1": ["polygamy"], "-4.7 25.6 7.4": ["warheads"], "0.1 10.2 6.2": ["ovation"], "7.7 15.2 4.7": ["photographing"], "7.2 14.4 10.4": ["predetermined"], "14.6 21.4 24.3": ["parasite"], "9.6 -1.1 0.9": ["flirted"], "-2.1 12.6 5.6": ["narratives"], "1.0 9.7 1.8": ["alluding", "accost"], "6.6 10.7 0.3": ["piloting"], "2.1 -1.2 -1.6": ["combed"], "-1.0 27.0 1.5": ["loyalist"], "12.0 7.5 -0.2": ["applauding"], "2.3 5.3 15.2": ["cubs"], "-5.8 4.2 -8.5": ["testimonies"], "4.8 2.3 3.4": ["im"], "7.6 12.0 3.1": ["backyards"], "6.3 8.9 8.3": ["cringe"], "14.2 -0.2 7.6": ["deluxe"], "3.8 18.1 7.9": ["overmatched"], "16.0 11.5 2.9": ["revolutions"], "10.1 9.9 14.4": ["slang"], "-10.0 9.5 -2.7": ["replying"], "15.1 6.7 4.3": ["thorny"], "9.1 12.4 4.3": ["shackled"], "3.5 5.8 9.3": ["interrupting"], "1.9 3.6 18.7": ["foodservice"], "6.3 12.6 8.9": ["impatience"], "5.3 -1.0 8.0": ["businesspeople"], "3.8 5.0 6.7": ["resuscitate"], "9.6 7.7 6.3": ["leans"], "7.9 3.5 7.5": ["rower"], "4.6 15.1 4.1": ["exaggerating"], "10.3 12.3 12.2": ["pundit"], "5.2 10.4 10.6": ["bureaucrat"], "0.7 11.7 31.6": ["appetizer"], "5.8 7.4 0.8": ["indecency", "innapropriate"], "7.8 4.0 12.2": ["cabs"], "-3.7 8.1 6.7": ["unassisted"], "7.3 2.9 0.5": ["chided"], "-2.7 11.7 7.2": ["storyteller"], "-4.1 10.8 -5.8": ["signatory"], "-3.1 9.6 0.3": ["basements"], "23.3 4.1 5.7": ["petrochemicals"], "3.3 8.6 0.4": ["expended"], "9.7 17.2 13.0": ["finite"], "-5.3 24.3 9.5": ["ideologies"], "21.8 6.5 12.3": ["wee"], "0.4 15.2 11.3": ["canon"], "7.8 12.7 5.5": ["shortcuts"], "5.1 21.4 8.7": ["reload"], "14.1 13.2 7.0": ["suffocating"], "2.7 9.9 3.1": ["negate"], "17.1 2.2 4.3": ["caved"], "-3.7 6.9 7.8": ["archeology"], "7.3 -1.6 2.2": ["surfacing"], "2.0 11.0 7.7": ["sporadically"], "6.8 -4.1 2.3": ["embezzling"], "-1.7 15.1 8.3": ["justifiable"], "3.8 0.5 13.6": ["consents"], "15.0 -2.5 7.7": ["bucking"], "12.3 11.0 15.9": ["sprawl"], "-3.3 12.5 5.3": ["goalkeepers"], "6.0 -2.9 6.8": ["soaps"], "13.4 11.2 5.8": ["forbidding"], "3.5 7.8 -0.2": ["luxuries"], "1.4 7.7 -2.1": ["refute"], "-0.0 7.1 13.2": ["vetoes"], "11.8 1.3 7.2": ["collage"], "11.0 0.5 4.5": ["unimpressed"], "5.6 2.1 28.3": ["pastry"], "6.5 6.2 1.0": ["staking"], "3.1 1.2 10.0": ["stranding"], "8.3 11.1 3.7": ["ghetto"], "9.5 8.6 31.0": ["carcass"], "17.5 2.4 8.9": ["tantalizing"], "2.8 11.5 -0.9": ["disband"], "16.8 29.1 3.7": ["unfriendly"], "32.0 25.1 21.6": ["beasts"], "3.4 12.1 -0.8": ["professed"], "13.2 0.8 7.1": ["dusted"], "11.4 -3.7 6.9": ["slimmer"], "3.1 -0.1 12.3": ["simulcast"], "24.9 9.5 36.9": ["penguins"], "4.0 -5.3 3.9": ["du"], "5.6 -0.4 -1.4": ["heartening"], "6.5 6.3 10.4": ["cupboard"], "7.5 6.3 5.6": ["schoolteacher"], "-3.1 2.3 -2.2": ["impartiality"], "9.1 16.4 6.1": ["methodically"], "0.4 5.6 -0.5": ["amicable"], "-6.7 9.1 1.8": ["esteem"], "10.4 11.6 -0.3": ["gauntlet"], "6.6 12.5 11.3": ["adore"], "4.1 7.8 5.8": ["bedtime"], "3.1 4.7 1.8": ["foreseen"], "9.5 5.7 7.3": ["charmed"], "1.8 15.1 4.3": ["doubly"], "20.0 -1.6 -1.7": ["mn"], "7.3 4.2 -0.5": ["elevating"], "-5.1 3.1 3.0": ["immigrated"], "6.0 18.8 7.5": ["scorn"], "-5.9 6.2 0.2": ["interfaith"], "0.4 7.9 4.0": ["spacing"], "5.2 14.2 6.1": ["unintended", "shrewed"], "-1.3 18.2 4.7": ["malice"], "10.7 6.1 8.1": ["steadied"], "3.5 5.7 8.2": ["impersonation"], "8.2 3.7 -2.0": ["chronicling"], "-5.9 8.5 8.8": ["cremated"], "4.4 15.1 8.2": ["intangible"], "8.9 10.1 24.8": ["reptiles"], "11.6 1.0 16.9": ["spruce"], "12.5 4.9 2.0": ["depots"], "8.7 7.5 13.6": ["broking"], "-0.1 -3.1 7.6": ["lapsed"], "2.7 3.2 3.3": ["gambled"], "15.3 11.0 12.0": ["lovable"], "2.3 6.8 3.2": ["coy"], "3.9 13.6 3.9": ["mastering"], "4.2 5.9 25.1": ["loaf"], "-3.8 1.1 8.1": ["cello"], "12.7 12.5 10.9": ["derelict", "grotesques"], "9.1 -2.0 7.9": ["waded"], "9.3 9.8 30.9": ["seawater"], "4.1 13.6 7.9": ["transcend"], "5.0 11.5 3.4": ["haste"], "7.1 5.9 -0.5": ["amalgamation"], "6.0 9.5 5.1": ["aerodynamic"], "11.0 14.2 -1.7": ["spontaneously"], "-1.7 3.8 -3.0": ["formative"], "-5.1 6.6 11.4": ["newscast"], "1.1 29.2 1.6": ["offensives"], "4.7 15.7 4.6": ["unquestionably"], "10.2 9.9 1.5": ["prodding"], "-5.5 0.4 7.2": ["twenties"], "3.3 -2.0 9.4": ["na"], "-2.0 3.4 5.2": ["metadata"], "9.0 22.2 7.5": ["quagmire"], "4.5 11.4 42.4": ["reefs"], "13.1 -1.9 0.5": ["rekindled"], "2.0 6.5 -0.1": ["ravine"], "9.8 9.7 1.0": ["succumbing"], "-2.2 14.6 16.1": ["pruning"], "18.2 6.8 10.8": ["plunges"], "0.6 9.3 6.7": ["invitational"], "3.8 7.9 7.1": ["nanoparticles"], "0.3 37.4 3.5": ["commando"], "15.7 9.9 15.0": ["alternately"], "16.9 19.9 13.9": ["nerd"], "-1.9 4.6 15.7": ["sheriffs"], "1.0 5.0 3.8": ["pamphlet"], "14.3 6.1 3.8": ["snuff"], "9.4 7.1 1.6": ["unassuming"], "9.1 -1.5 4.7": ["rags"], "0.1 7.8 16.3": ["manga"], "7.0 7.6 4.7": ["digestive"], "3.2 6.8 -2.7": ["fathered"], "14.9 9.7 20.6": ["mash"], "-3.8 12.4 6.3": ["friendlies"], "5.8 6.1 7.4": ["prodded"], "7.7 7.8 11.2": ["concocted"], "-2.4 4.7 3.4": ["particulars"], "8.0 7.1 6.2": ["gearbox"], "4.3 17.0 9.4": ["someplace"], "1.9 16.2 3.5": ["shootouts"], "11.6 2.8 4.3": ["suffocated"], "-0.5 2.4 -0.1": ["credence"], "0.7 10.1 8.1": ["kickers"], "5.4 4.3 3.9": ["surpasses"], "6.1 10.6 14.3": ["downtrend"], "8.6 1.7 7.4": ["pondered"], "32.1 11.9 22.1": ["gorilla"], "-4.7 13.4 5.4": ["wiretaps"], "14.0 17.7 11.8": ["clutches"], "4.2 6.2 5.9": ["nullified"], "5.1 8.6 25.9": ["cinnamon"], "1.1 20.4 5.2": ["affront"], "2.0 0.3 21.2": ["nurseries"], "17.6 4.9 6.4": ["folds"], "-7.0 9.4 1.0": ["rehearsed"], "8.6 9.9 3.8": ["lobbed"], "0.8 16.2 -1.7": ["tenets"], "2.0 3.8 12.0": ["sequencing"], "26.9 11.3 18.0": ["goddess"], "10.9 5.1 18.2": ["takeaway"], "14.6 7.5 9.0": ["bonfire"], "11.2 4.0 1.9": ["belated"], "2.5 9.7 1.7": ["pencils"], "5.9 6.6 2.8": ["rhythmic"], "10.5 10.5 11.5": ["gimmicks"], "14.0 3.1 9.0": ["prod"], "4.4 1.9 27.1": ["carcasses"], "17.4 -4.0 4.8": ["patterned"], "13.3 31.8 6.5": ["insidious"], "8.6 2.5 16.8": ["sheen"], "-5.9 18.6 -0.6": ["sympathies"], "-9.0 10.9 4.4": ["constables"], "0.9 0.7 -2.8": ["refinement"], "5.9 10.6 6.7": ["meteorological"], "2.1 22.8 7.1": ["protagonists"], "9.0 0.7 23.5": ["cupcakes"], "5.5 6.7 1.8": ["blockage"], "7.3 2.8 -0.8": ["copyrights"], "12.3 15.6 9.8": ["licking"], "-2.6 14.0 21.5": ["orchard"], "-3.8 14.4 3.5": ["disliked"], "-2.2 4.3 6.2": ["reprocessing"], "-1.4 6.7 -3.3": ["translators"], "-6.5 2.1 3.9": ["manuscripts"], "4.1 12.9 5.3": ["transcends"], "13.3 5.0 5.6": ["jolted"], "0.6 0.5 13.8": ["cadmium"], "-0.3 1.4 3.4": ["gymnast"], "-2.0 11.8 9.8": ["secession"], "19.0 1.4 4.1": ["peddling"], "7.7 4.7 3.2": ["slideshow"], "6.9 -0.2 7.2": ["gigabytes"], "15.6 14.6 9.7": ["animations"], "4.0 13.4 5.0": ["obscenity"], "-2.4 5.5 8.8": ["barber"], "-0.7 14.8 3.2": ["constraint"], "3.7 13.9 8.0": ["bragging"], "18.3 4.6 3.9": ["gurus"], "3.9 3.3 4.1": ["instituting"], "29.6 21.5 25.7": ["spiders"], "13.5 8.3 9.0": ["hubby"], "0.9 4.8 -2.5": ["interactivity"], "6.1 5.3 13.2": ["socket"], "7.0 10.9 5.7": ["shackles"], "2.4 -0.9 5.5": ["homemaker"], "5.1 11.3 9.2": ["bled"], "-1.8 4.3 0.7": ["errands"], "5.4 7.2 4.0": ["conjure"], "5.0 11.7 2.1": ["decipher"], "9.9 4.9 5.3": ["eclipsing"], "10.6 5.9 -0.1": ["sweltering"], "15.9 13.3 11.3": ["orbiting"], "-0.4 0.9 10.6": ["dropout"], "-2.7 20.4 -3.0": ["intercepts"], "10.4 4.8 38.2": ["peach"], "0.6 2.4 3.0": ["bureaus"], "-0.8 2.3 11.2": ["rerun"], "11.2 -2.5 14.9": ["overdone"], "4.6 0.3 0.3": ["ingested"], "10.4 3.4 2.5": ["picket"], "4.9 18.4 5.1": ["illumination"], "0.1 4.0 18.3": ["snowboard"], "5.3 -1.9 2.7": ["recyclable"], "3.5 11.6 11.6": ["shockingly"], "-1.8 2.3 46.4": ["aquaculture"], "-1.7 19.9 4.8": ["secularism"], "9.2 15.4 5.5": ["abyss"], "4.9 8.9 7.4": ["freeways"], "0.6 7.0 13.6": ["downturns"], "4.8 11.8 12.3": ["plows", "mascherano"], "-6.0 1.4 5.3": ["adjournment"], "3.7 15.0 14.6": ["ruck"], "10.1 14.9 13.5": ["gosh"], "10.8 4.6 1.4": ["brightly"], "1.3 1.9 -0.0": ["concierge"], "21.1 9.6 27.6": ["steaming"], "3.9 4.7 -4.4": ["trafficked"], "13.0 10.7 2.8": ["unlisted"], "19.5 16.9 19.0": ["dart"], "11.2 3.1 17.3": ["refrigerated"], "3.4 1.0 6.0": ["grads"], "16.4 8.8 6.8": ["innocuous"], "8.6 0.4 2.6": ["shampoo"], "14.2 2.7 -3.9": ["undertakings"], "4.6 27.9 6.9": ["righteous"], "4.5 5.7 11.0": ["grumbling"], "4.8 3.3 4.3": ["polishing"], "10.5 6.0 13.3": ["relic"], "3.0 6.8 7.0": ["unaffordable"], "-6.1 23.1 0.1": ["apprehend"], "7.4 0.5 11.0": ["mixer"], "15.3 11.8 1.8": ["oblivion"], "6.6 10.2 -6.1": ["decentralized"], "3.0 7.3 9.4": ["destitute"], "1.7 3.1 3.0": ["goings"], "3.9 33.7 1.0": ["patriots"], "-1.1 26.0 -4.9": ["slander"], "8.2 4.3 19.3": ["pastries"], "-3.5 7.5 10.2": ["deductibles"], "-1.7 16.9 18.8": ["fastballs"], "-7.6 0.9 5.2": ["archival"], "0.1 0.9 2.2": ["commuted"], "-4.6 8.3 -0.1": ["religiously"], "15.2 15.0 12.9": ["perpetually"], "1.1 8.1 12.0": ["cricketing"], "5.0 -1.8 12.4": ["tubing"], "-0.4 -0.3 3.5": ["orchestras"], "3.3 18.3 0.4": ["reprehensible"], "10.7 13.4 2.0": ["intrinsic"], "10.1 14.2 3.5": ["screenshots"], "-0.2 11.6 2.6": ["eras"], "12.0 8.5 6.9": ["unattractive"], "1.0 6.7 3.4": ["testy"], "3.7 2.3 0.7": ["impassioned"], "7.5 14.1 10.3": ["hemisphere"], "11.9 2.7 10.5": ["bagging"], "9.0 7.2 -0.9": ["redefining"], "9.1 -6.5 7.5": ["auctioning"], "12.1 3.5 3.4": ["reinvigorate"], "1.3 2.1 5.5": ["cosmopolitan"], "15.2 9.6 9.6": ["dueling"], "8.8 4.4 6.4": ["geologists"], "12.6 12.4 5.7": ["intensifies"], "8.1 -3.9 6.1": ["www"], "0.0 7.0 8.4": ["unplanned"], "-7.9 12.8 0.9": ["misunderstandings"], "7.0 8.9 4.5": ["rediscovered"], "-2.9 20.9 3.8": ["criminality"], "9.9 11.4 13.5": ["unbroken"], "1.3 7.7 -4.2": ["absentia"], "1.5 8.6 -3.3": ["impair"], "-7.7 10.3 1.3": ["constitutionally"], "2.6 1.2 1.7": ["enforceable"], "7.1 4.5 9.2": ["pedals"], "1.9 22.0 12.0": ["pawn"], "3.1 -0.1 8.0": ["boilers"], "13.5 7.9 4.3": ["throngs"], "-3.5 7.1 2.9": ["modesty"], "8.1 11.3 -2.6": ["wipes"], "-5.0 12.8 -2.8": ["forthright"], "15.7 -0.8 8.1": ["storefronts"], "8.5 3.2 6.2": ["tendinitis"], "11.9 6.2 3.0": ["concourse"], "9.4 12.7 5.6": ["barricade"], "21.0 21.3 30.3": ["critters"], "6.3 8.3 -3.0": ["pressurized"], "5.7 7.9 7.6": ["bottleneck"], "4.5 7.2 6.4": ["verifiable"], "-2.7 11.5 0.5": ["impeached"], "11.2 6.4 18.9": ["tarp", "spirea"], "5.2 3.8 8.9": ["squabbling"], "8.7 -1.0 8.2": ["gigabyte"], "-6.7 -2.5 -7.2": ["seconded"], "8.6 16.2 6.3": ["pedophiles"], "13.9 24.9 6.0": ["unforgiving"], "4.2 11.5 4.8": ["pandering"], "8.7 -5.7 -2.6": ["inaugurate"], "9.3 6.9 17.9": ["skateboard"], "4.7 12.5 4.0": ["coded", "citoyen"], "23.2 20.2 8.9": ["hideous"], "-0.8 -2.6 14.6": ["seasonality"], "2.8 14.6 7.1": ["irreplaceable"], "11.3 14.6 8.2": ["shaded"], "4.3 17.0 4.3": ["disoriented"], "10.0 4.9 8.7": ["paring"], "8.9 -5.4 6.0": ["languished"], "6.6 14.2 8.6": ["mischievous"], "-0.1 4.2 22.8": ["canola"], "9.2 8.2 3.4": ["disconcerting"], "2.0 2.5 1.4": ["symptomatic"], "7.9 1.3 2.5": ["upmarket"], "10.3 11.4 2.8": ["tagline"], "5.2 -6.9 14.6": ["cartons"], "3.5 11.6 8.2": ["ruble"], "4.0 2.8 11.9": ["capsized"], "0.0 2.2 -5.0": ["abreast"], "1.2 9.3 -2.0": ["conciliatory"], "-2.6 2.1 11.0": ["emcee", "fredericksburg"], "5.2 6.4 13.8": ["complexion"], "6.9 2.3 -0.1": ["aroused"], "2.7 11.0 29.2": ["marshes"], "6.1 9.4 2.9": ["sexist"], "11.6 -2.5 9.2": ["underpinning"], "10.5 -1.0 9.4": ["mirroring"], "11.1 2.6 5.1": ["odyssey"], "0.7 0.8 2.9": ["tertiary"], "0.1 8.1 2.3": ["recoverable"], "4.5 2.7 8.3": ["molding"], "6.8 6.6 3.2": ["onward"], "5.7 2.3 5.0": ["trickling"], "5.1 13.3 1.7": ["reboot", "modularizing"], "0.3 3.7 10.7": ["scooters"], "4.4 15.6 4.7": ["mouthpiece"], "7.9 11.0 10.6": ["nick"], "10.4 4.2 3.8": ["piped"], "2.6 -0.3 26.7": ["pearls"], "10.2 7.0 8.5": ["intricacies"], "14.5 3.9 38.3": ["pineapple"], "0.9 2.6 -5.1": ["inaccuracies"], "19.3 5.3 17.1": ["whacked"], "10.3 3.2 11.3": ["blush"], "1.5 7.6 7.4": ["rugs"], "11.8 -4.6 -2.0": ["allay"], "2.2 -3.3 11.6": ["tendering"], "16.0 15.3 6.6": ["benefactor"], "-1.7 8.5 16.8": ["bud"], "15.0 0.7 8.9": ["stately"], "2.6 7.6 13.1": ["ringside"], "10.6 12.2 7.9": ["montage"], "16.7 6.1 28.9": ["reindeer"], "19.6 14.7 5.6": ["explodes"], "-1.4 7.1 1.8": ["specialization"], "-8.7 2.7 16.5": ["mares"], "4.1 11.3 3.2": ["rediscover"], "-1.2 9.7 -0.7": ["composing"], "12.4 8.4 -0.1": ["frauds"], "6.9 9.9 15.3": ["tongues"], "-0.9 3.6 9.1": ["epidemiologist"], "19.0 10.8 0.5": ["ticker"], "-0.3 14.4 -2.6": ["affirmative"], "10.1 8.7 22.1": ["kettle"], "9.3 16.1 8.1": ["pounce"], "17.3 9.4 39.5": ["watermelon"], "2.8 12.3 6.2": ["aberration"], "6.9 5.2 10.3": ["masterpieces"], "5.6 9.0 12.4": ["cartoonist"], "1.1 11.8 5.9": ["profane"], "15.6 16.4 15.3": ["ledge"], "-0.8 2.6 1.0": ["conductors"], "4.9 10.9 4.6": ["shortcut"], "-0.2 5.0 17.7": ["wreaths"], "-6.8 26.9 7.7": ["deterrence"], "1.3 3.3 12.7": ["guardrail"], "4.9 3.7 11.1": ["awry"], "23.7 6.7 7.4": ["dizzying"], "7.2 7.5 14.1": ["sprinkle"], "4.0 8.9 4.9": ["hurler"], "-13.2 9.6 3.5": ["millage"], "12.5 8.5 -1.6": ["wooing"], "-6.3 3.6 14.4": ["cremation"], "14.2 4.3 17.9": ["skimming"], "-3.8 5.5 -3.7": ["substantiate"], "14.2 15.7 5.8": ["silhouette"], "8.7 5.9 8.8": ["stepdaughter"], "17.4 4.7 12.1": ["sputtering"], "6.3 9.1 6.7": ["affable"], "-6.2 7.1 3.1": ["confided"], "6.2 5.2 -2.1": ["suggestive"], "-5.9 2.7 3.0": ["disapproved"], "11.5 8.4 6.1": ["sharpened"], "-3.3 12.2 8.8": ["bisexual"], "6.8 6.5 11.1": ["indexing"], "0.9 -9.9 -2.2": ["testimonials"], "5.3 1.6 2.0": ["converter"], "10.5 1.6 8.2": ["skyrocket"], "-5.1 6.2 4.6": ["pediatrics"], "-4.0 4.5 9.0": ["harmonies"], "1.2 15.8 8.7": ["unequal"], "1.9 10.2 4.7": ["devaluation"], "18.2 3.4 6.4": ["boomed"], "10.4 7.0 11.6": ["safari"], "18.2 14.6 14.7": ["crunching"], "28.4 3.6 3.8": ["dwarfed"], "1.7 10.3 5.0": ["newsmen"], "8.8 11.1 5.8": ["insulate"], "13.1 11.8 7.3": ["mover"], "4.6 4.5 11.8": ["jeweler"], "2.4 8.8 16.2": ["cider"], "1.8 12.5 5.1": ["claimant"], "-2.4 3.0 6.2": ["workday"], "18.2 3.7 5.4": ["wedged"], "18.7 1.4 6.7": ["ripple"], "12.1 10.5 9.7": ["blokes"], "-2.1 -3.1 6.5": ["reconsidered"], "15.4 13.1 14.4": ["rover"], "-2.9 3.2 8.3": ["dehydrated"], "1.3 18.3 -1.1": ["distorting"], "13.0 -4.8 4.7": ["dimmed"], "3.9 3.2 9.3": ["diaper"], "16.9 5.8 7.7": ["stomped"], "-1.2 13.3 15.9": ["longs"], "3.6 -3.2 5.6": ["fittings"], "8.7 16.3 8.9": ["callous"], "7.4 3.4 6.5": ["leisurely"], "-0.5 9.9 14.6": ["rations"], "-3.4 12.8 4.4": ["handoff"], "2.7 11.4 7.3": ["cybersecurity"], "6.4 3.0 4.9": ["jockeying"], "12.4 2.0 -5.5": ["renaming"], "14.1 0.8 2.4": ["scintillating"], "5.9 6.9 11.2": ["angering"], "9.3 30.0 5.1": ["haters"], "23.9 3.2 7.0": ["minuscule"], "-1.7 17.9 3.2": ["pretense"], "19.0 9.4 2.9": ["reshaping"], "-2.0 12.1 3.7": ["predictor"], "2.9 3.6 5.7": ["stables"], "14.2 11.7 11.7": ["fragility"], "9.4 8.4 3.8": ["subways"], "7.3 -1.7 6.1": ["cram"], "8.2 -2.7 6.5": ["tutorials"], "0.0 8.1 6.6": ["blemish"], "12.8 3.9 13.5": ["gov"], "5.1 12.7 4.9": ["nicknames"], "-3.4 9.9 12.7": ["bicyclists"], "4.4 3.4 9.2": ["conferencing"], "5.7 6.7 3.0": ["unwinding"], "11.2 27.1 8.7": ["jungles"], "4.4 9.9 9.3": ["recede"], "-2.7 7.2 22.9": ["phosphorus"], "13.9 6.0 8.3": ["patchy"], "6.2 11.8 9.2": ["genetically"], "7.4 7.7 3.2": ["scolded"], "11.5 8.7 6.4": ["waterproof"], "11.5 8.9 11.2": ["stereotypical"], "-0.9 7.0 9.7": ["saliva"], "1.7 13.6 3.0": ["overtly"], "13.9 10.7 5.1": ["rips"], "-1.3 13.1 14.8": ["lineout"], "-2.1 10.2 5.1": ["endpoint"], "3.9 5.4 6.6": ["changeover"], "10.6 -4.1 -0.9": ["scrutinizing"], "5.6 15.3 0.1": ["desist"], "14.9 -2.8 14.2": ["studded"], "-1.9 2.0 15.3": ["simmer"], "-5.1 9.9 22.5": ["tributaries"], "1.7 6.0 3.3": ["stimulates"], "0.5 12.9 4.2": ["compels"], "-5.6 10.9 7.5": ["appraiser"], "7.8 -2.9 6.8": ["massages"], "8.8 25.8 3.9": ["terrorizing"], "7.8 6.6 0.8": ["scour"], "6.5 7.9 11.8": ["thighs"], "11.2 7.0 12.4": ["skittish"], "10.1 1.8 9.7": ["thrash"], "6.6 4.4 2.4": ["rekindle"], "5.2 7.6 0.1": ["fightback"], "0.9 8.5 0.8": ["directorate"], "1.1 6.4 4.9": ["screeners"], "-5.5 15.7 8.3": ["alienation"], "5.5 0.7 2.2": ["reining"], "3.9 24.2 0.2": ["willfully"], "9.8 1.6 12.3": ["kitty"], "1.6 5.9 7.7": ["ply"], "2.1 24.4 2.4": ["admirer"], "-7.2 7.0 5.5": ["overdraft"], "1.0 9.3 6.9": ["abdominal"], "9.9 3.4 7.4": ["exposition"], "8.4 16.8 10.2": ["gridiron"], "7.0 7.4 8.0": ["balconies"], "-0.5 9.0 9.0": ["motorbikes"], "4.3 4.9 11.0": ["dwindle"], "18.3 14.1 7.6": ["lifeless"], "1.3 11.0 0.1": ["reformer"], "5.9 27.6 9.5": ["instinctively"], "1.7 23.5 7.8": ["incursions"], "-2.1 3.1 3.3": ["revisiting"], "13.2 13.8 6.2": ["pedestal"], "-11.1 -0.6 2.3": ["officiate"], "16.7 -3.0 1.1": ["abuzz"], "2.7 8.4 3.1": ["cartridge"], "3.1 9.1 2.2": ["restraining"], "17.7 5.3 18.6": ["striped", "dixie"], "8.8 5.5 19.2": ["anchoring"], "-1.5 5.1 4.1": ["plagiarism"], "4.6 3.4 2.6": ["debentures"], "7.3 7.0 0.0": ["dizziness"], "-8.2 7.9 6.3": ["reassessment"], "3.7 3.5 1.6": ["painless"], "-3.3 8.3 3.5": ["honoree"], "6.9 8.3 -0.7": ["revitalizing"], "-11.1 -3.7 11.2": ["methadone"], "7.0 16.8 6.7": ["proportional"], "6.4 8.2 3.1": ["evocative"], "9.1 10.4 13.9": ["machete"], "1.2 6.4 14.3": ["cialis"], "14.0 12.9 11.2": ["dudes"], "13.2 15.3 9.1": ["planetary"], "-1.8 9.1 5.1": ["brow"], "6.0 8.2 8.4": ["midcourt"], "-1.6 18.0 5.8": ["overthrown"], "6.1 5.3 5.7": ["mishandling"], "11.0 7.5 5.6": ["narrows"], "6.4 2.3 9.2": ["bustle"], "8.0 5.0 4.3": ["keenly"], "15.0 -1.3 0.0": ["inks"], "8.5 14.0 5.3": ["twister"], "-14.4 2.9 12.6": ["ordination"], "4.7 -2.6 -1.8": ["receivable"], "8.8 1.9 6.5": ["embarks"], "10.5 10.9 -3.2": ["repositioning"], "8.6 2.8 28.2": ["sausages"], "-3.7 14.6 5.5": ["polarization"], "11.7 -2.1 4.4": ["socialite"], "3.7 2.5 -0.1": ["floodgates"], "11.4 16.3 7.3": ["audacity"], "5.7 6.3 11.6": ["compounding", "gaane"], "-3.9 9.9 4.2": ["franchised"], "-5.6 9.7 7.1": ["doable"], "1.1 9.0 8.6": ["disenfranchised"], "1.0 9.6 8.9": ["exasperated"], "10.2 8.1 -3.2": ["redefined"], "5.8 9.1 4.3": ["bragged"], "12.8 10.4 7.4": ["throes"], "8.7 1.9 12.4": ["primer"], "-6.5 7.0 6.8": ["anesthetic"], "0.3 5.0 6.7": ["jaded"], "3.8 28.6 1.4": ["battalions"], "6.1 9.8 12.1": ["microprocessors"], "19.2 9.5 -4.2": ["sniffing"], "-0.6 3.5 17.2": ["vacationers"], "12.4 13.8 1.5": ["illuminating"], "4.5 3.6 3.7": ["quintet"], "18.3 15.2 5.2": ["strongman"], "-0.2 4.6 8.4": ["sewerage"], "12.5 1.6 4.2": ["nonbinding"], "-3.9 9.1 13.8": ["chemo"], "-6.6 16.1 4.8": ["quarrel"], "6.3 5.5 9.4": ["holidaymakers"], "0.3 4.3 14.4": ["pints"], "2.3 12.0 7.0": ["announcers"], "0.9 4.4 1.8": ["aspirants"], "-1.3 2.3 9.3": ["malnourished"], "18.3 5.7 11.2": ["plumes"], "7.9 17.0 2.7": ["infinitely"], "7.7 -0.0 0.5": ["underperform"], "0.9 19.0 7.1": ["eradicated"], "0.8 25.3 8.0": ["creed"], "11.5 14.5 5.6": ["admiring"], "8.6 3.3 1.0": ["envisages"], "7.0 13.0 4.8": ["misdeeds"], "2.6 19.5 4.1": ["visceral"], "4.8 13.2 6.4": ["lash"], "-0.8 1.8 8.4": ["indulged"], "-0.9 1.4 10.7": ["refereeing"], "0.4 7.0 12.4": ["campgrounds"], "5.2 -0.8 4.3": ["sportswear"], "14.9 -0.2 8.0": ["galore"], "6.6 2.8 13.5": ["pinched"], "12.3 12.4 4.5": ["unfettered"], "4.3 4.0 4.8": ["stoppages"], "-1.4 10.5 0.8": ["involuntary"], "6.1 5.3 3.2": ["rejuvenate"], "-0.2 12.0 9.8": ["federalism"], "7.8 11.6 6.1": ["masculine"], "7.7 12.6 27.9": ["vine"], "4.8 3.7 4.4": ["op"], "0.7 4.2 10.5": ["grazed"], "-3.2 11.2 -1.4": ["admires"], "12.6 19.8 1.2": ["embodiment"], "9.9 1.9 6.3": ["bankroll"], "12.7 -0.3 2.0": ["shakeup"], "-6.6 -5.7 -1.0": ["deliberated"], "6.1 5.8 10.6": ["complicating"], "0.1 6.3 1.3": ["competencies"], "8.9 9.6 12.0": ["courtship"], "3.7 11.9 2.1": ["pollute"], "15.1 17.6 14.7": ["wrecking"], "3.3 4.3 8.4": ["hazy"], "3.4 17.4 9.8": ["arbitrarily"], "13.4 9.1 12.5": ["telcos"], "1.7 -5.0 -0.7": ["formalized"], "10.5 9.0 5.5": ["bolder"], "4.6 7.3 5.7": ["meteorologists"], "11.2 -0.7 6.0": ["biodegradable"], "13.3 2.7 4.2": ["bribing"], "0.6 5.2 28.0": ["swine"], "7.0 -3.6 17.8": ["linen"], "12.3 22.4 2.3": ["frighten"], "11.1 5.9 2.7": ["veiled"], "12.0 14.7 14.6": ["retrieving"], "7.1 13.5 6.4": ["dribbling"], "9.5 30.2 11.0": ["cunning"], "10.7 9.7 8.8": ["roost", "tricolor"], "2.3 8.3 19.4": ["primates"], "-1.2 2.0 -4.1": ["collaboratively"], "-3.3 3.9 23.3": ["lambs"], "3.4 1.2 6.1": ["fluctuated"], "3.3 9.1 8.5": ["temblor"], "3.2 31.3 3.9": ["fascism"], "4.1 4.7 13.9": ["tokens"], "13.7 5.9 28.6": ["slabs"], "0.1 4.7 5.6": ["orchestral"], "3.3 9.8 3.2": ["aches"], "-14.0 1.1 8.1": ["multifamily"], "4.6 1.1 7.9": ["embroidered"], "-2.1 7.2 12.5": ["fluctuation"], "10.0 7.5 -0.8": ["blacklist"], "-2.2 11.7 12.8": ["mike"], "-0.9 4.8 6.0": ["preliminaries"], "17.0 11.1 10.5": ["mesmerizing"], "3.2 15.2 7.5": ["spares"], "-0.2 10.5 11.7": ["ebb"], "15.0 -0.2 5.6": ["spotlights"], "21.2 5.4 12.0": ["centimeter"], "8.7 1.4 7.9": ["commences"], "-1.1 15.2 4.7": ["stateside"], "15.2 12.0 11.3": ["hacks"], "11.9 3.0 21.8": ["grocers"], "9.2 10.9 2.4": ["downtrodden"], "5.0 8.6 8.5": ["hue"], "17.7 8.5 12.1": ["chipmaker"], "8.3 13.8 3.6": ["airliners"], "9.2 20.5 4.0": ["enforcer"], "-2.6 8.9 8.2": ["attendee"], "-1.7 -2.2 -2.5": ["vouch"], "4.5 15.7 7.8": ["absurdity"], "13.9 5.0 22.5": ["reels"], "2.0 21.1 -0.1": ["implicitly"], "-1.7 10.5 9.3": ["pancreas"], "9.4 13.7 10.4": ["drifts"], "6.3 11.2 4.4": ["outweighs"], "17.2 1.0 1.7": ["ripples"], "3.5 16.4 -0.5": ["polarizing"], "1.1 20.4 3.9": ["preconditions"], "-1.9 14.7 8.2": ["quotation"], "17.8 11.0 6.1": ["forays"], "4.8 12.7 5.5": ["peloton"], "-2.3 2.1 6.8": ["tailoring"], "16.1 10.1 20.1": ["cone"], "11.9 -5.6 5.7": ["strut"], "-2.4 7.1 -0.9": ["excise"], "11.6 5.9 0.2": ["shined"], "3.4 2.2 -3.4": ["monetization"], "4.2 7.4 12.3": ["celeb"], "-1.4 0.9 -2.2": ["cardiology"], "16.3 19.6 8.4": ["aversion"], "5.5 1.8 -4.7": ["blazed"], "-2.8 2.2 14.0": ["weightlifting"], "3.4 14.2 6.0": ["flak"], "0.2 20.3 2.5": ["moreover"], "0.7 0.3 8.3": ["beautification"], "6.5 13.8 2.3": ["ingrained"], "7.4 9.2 5.9": ["graciously"], "18.5 8.1 11.2": ["puff"], "4.9 5.0 32.9": ["maple"], "6.0 6.2 13.9": ["brewers"], "9.5 5.7 5.2": ["floored"], "-9.8 14.1 7.7": ["prerogative"], "-5.1 19.6 3.7": ["loyalties"], "1.3 3.4 3.1": ["classifications"], "10.9 16.6 15.7": ["underside"], "6.3 4.5 0.1": ["enlargement"], "20.4 7.0 14.7": ["rectangular"], "6.6 0.2 10.5": ["pomp"], "13.7 8.1 12.1": ["slumps"], "10.2 8.6 2.2": ["flashpoint"], "10.4 6.0 -1.1": ["assailed"], "3.1 11.2 20.6": ["keel"], "5.5 1.0 3.8": ["metering"], "9.4 7.0 5.5": ["reclaiming"], "1.7 2.3 4.1": ["anthropology"], "11.9 11.4 6.2": ["sonic"], "11.7 12.8 0.8": ["infecting"], "19.3 -1.0 1.8": ["prodigy"], "6.2 38.1 1.4": ["assassins"], "5.7 1.3 1.4": ["automates"], "2.2 17.8 9.0": ["unintentionally"], "15.1 8.1 3.3": ["tattered"], "9.5 6.6 9.1": ["trepidation", "braes"], "8.7 3.8 2.1": ["hiccups"], "6.3 17.6 6.0": ["ruse"], "18.5 3.9 4.5": ["propelling"], "8.9 14.1 11.0": ["karma"], "-2.0 10.6 -2.7": ["liquidated"], "9.9 12.6 4.7": ["unknowingly"], "5.7 1.3 3.6": ["yrs"], "8.5 10.0 3.1": ["overvalued"], "3.7 2.2 -1.9": ["impropriety"], "17.2 19.3 12.7": ["phantom"], "15.1 10.1 14.1": ["decaying"], "2.8 2.3 -1.1": ["hassles"], "-4.4 10.3 2.8": ["cardio"], "16.8 1.7 -3.0": ["trumpeted"], "1.2 7.9 29.2": ["savory"], "-11.0 10.5 -0.5": ["attainable"], "-5.0 0.7 5.5": ["reconsideration"], "0.8 7.4 11.7": ["excavated"], "-3.4 0.2 -6.8": ["interacted"], "-2.5 12.7 3.7": ["autocratic"], "-1.1 14.4 -0.4": ["homophobic"], "1.8 35.5 9.0": ["innocents"], "5.0 5.6 12.7": ["tango"], "2.6 14.5 2.6": ["logically"], "3.8 12.7 3.1": ["nodding"], "10.9 1.9 6.6": ["stirs"], "9.6 -3.5 -5.1": ["commercialized"], "-0.6 0.2 -1.0": ["rewritten"], "-0.1 -1.1 2.9": ["infuse"], "4.0 17.2 3.6": ["airlift"], "5.6 17.4 10.3": ["bravado"], "-4.8 0.6 4.2": ["deferring"], "10.7 13.1 6.3": ["archaic"], "5.5 18.9 1.1": ["thorn"], "10.1 11.5 4.9": ["bends"], "6.3 12.9 1.1": ["emitting"], "0.3 -3.5 -0.7": ["queried"], "4.9 23.6 5.7": ["leftists"], "-0.3 15.4 0.8": ["baptism"], "20.5 7.1 17.7": ["jolly"], "5.0 12.4 13.6": ["bitterly"], "14.9 7.9 4.7": ["widens"], "2.7 6.1 -1.2": ["deservedly"], "7.3 7.4 5.7": ["unduly"], "3.5 1.2 -0.8": ["certifying"], "2.3 4.1 8.6": ["checkbook"], "0.8 1.7 19.8": ["skillet"], "12.6 2.6 1.1": ["beefing"], "7.9 8.2 1.0": ["rants"], "5.7 4.3 2.9": ["originates"], "1.4 11.7 1.3": ["firstly"], "16.7 6.6 11.1": ["fairytale"], "8.7 16.7 9.8": ["venom"], "2.7 15.8 3.3": ["annoy"], "6.6 18.9 10.5": ["propulsion"], "15.0 1.1 4.8": ["popularized"], "-5.8 2.8 -2.2": ["clarifies"], "23.5 13.8 9.1": ["magically"], "1.5 4.7 7.5": ["netball"], "5.6 10.4 5.7": ["mutilated"], "-5.4 20.5 1.8": ["confidant"], "1.7 8.7 4.0": ["wavering"], "8.7 8.4 8.9": ["walkways"], "-1.0 15.3 1.9": ["diminishes"], "19.1 26.9 2.5": ["conquering"], "15.9 8.2 9.5": ["squat"], "8.5 12.1 8.0": ["wildcard"], "9.3 19.4 7.7": ["catastrophes"], "9.7 11.8 8.6": ["fumbling"], "6.6 -3.7 2.9": ["enticed"], "0.6 10.4 -5.4": ["hounded"], "13.4 0.0 8.6": ["culminates"], "4.0 5.7 17.0": ["thrift"], "4.7 11.7 10.5": ["coworkers"], "6.5 6.6 6.4": ["marries"], "1.3 0.5 10.3": ["offbeat"], "7.4 25.5 1.2": ["torment"], "-9.4 5.4 2.6": ["soloist"], "-2.6 11.8 13.4": ["goaltenders"], "-4.9 17.7 3.8": ["premeditated"], "1.0 9.2 3.9": ["tiebreak"], "10.1 11.2 8.1": ["locale"], "-5.0 7.0 9.3": ["socioeconomic"], "8.8 7.2 12.8": ["wading"], "7.4 28.0 5.1": ["nefarious"], "7.6 10.3 3.0": ["fractious"], "2.7 9.9 -0.5": ["stairwell"], "3.2 16.2 4.7": ["forgets"], "7.2 2.3 -4.5": ["refurbishing"], "5.2 39.0 6.2": ["mortal"], "18.5 4.5 0.7": ["adorn"], "-4.4 5.7 -1.0": ["troubleshooting", "roominess"], "-0.9 3.9 7.9": ["uterus"], "-4.6 14.2 2.7": ["idealistic"], "4.2 8.5 7.6": ["grandsons"], "16.9 23.1 8.8": ["hegemony"], "-0.1 17.1 6.1": ["unranked"], "8.6 9.6 1.0": ["westward"], "10.3 0.9 10.9": ["bottoming"], "-10.7 -0.3 -0.0": ["mentored"], "-1.3 10.6 22.0": ["paddling"], "14.3 1.0 10.2": ["fetching"], "14.8 6.9 0.2": ["multifaceted"], "7.2 9.1 11.7": ["prospecting"], "2.3 5.7 6.8": ["precipitated"], "3.9 -0.4 -7.0": ["applauds"], "19.1 2.4 12.7": ["psychedelic"], "16.1 -1.5 16.9": ["glitter"], "-1.4 1.3 8.1": ["ranches"], "-9.3 13.6 5.2": ["treatable"], "4.1 3.7 10.9": ["irreverent"], "16.9 5.9 6.4": ["erection"], "4.3 8.9 1.7": ["precedents"], "15.5 8.3 8.7": ["corral"], "1.4 11.2 2.9": ["crucially"], "20.1 4.1 8.0": ["spiking"], "-4.4 13.8 4.0": ["overthrew"], "9.5 4.0 5.6": ["clutched"], "0.0 10.9 -0.0": ["rotations"], "-1.5 10.3 4.3": ["chords"], "-1.8 5.5 1.9": ["reinvest"], "-6.6 1.4 12.1": ["chipsets"], "-2.8 5.9 2.5": ["designations"], "3.5 15.4 23.9": ["sinker"], "-11.0 3.1 9.2": ["dropouts"], "9.1 7.9 10.9": ["curl"], "13.1 10.9 8.4": ["gazing"], "9.3 10.0 9.8": ["nailing"], "1.8 1.3 2.1": ["rollback"], "-5.0 -0.7 0.7": ["appraised"], "5.5 14.8 10.5": ["pry"], "16.0 10.3 6.7": ["crappy"], "2.2 9.7 0.6": ["underdeveloped"], "21.8 0.3 12.6": ["encased"], "8.3 5.8 2.4": ["spaced"], "11.9 14.3 9.4": ["wretched"], "6.1 -1.0 13.7": ["slippers"], "0.8 9.5 14.2": ["naught"], "4.6 14.4 2.1": ["recaptured"], "4.9 10.7 13.1": ["rhymes"], "5.4 9.2 17.2": ["sandy"], "-4.1 8.0 25.4": ["seedlings"], "16.3 9.2 3.7": ["swaying"], "-7.7 12.9 -4.4": ["parliamentarian"], "0.7 18.1 9.5": ["epidemics"], "2.8 7.8 19.9": ["culling"], "12.2 9.7 9.4": ["backboard"], "-1.1 1.1 36.7": ["peaches"], "8.7 7.7 0.8": ["dissipate"], "2.8 7.3 14.1": ["studs"], "11.0 4.2 -0.1": ["lapped"], "2.3 5.2 8.3": ["lamenting"], "7.1 -0.2 9.2": ["arrays"], "-2.1 13.7 1.8": ["wiretapping"], "-0.1 0.4 8.5": ["cropping"], "4.8 3.7 -4.3": ["aspires"], "11.6 2.6 14.3": ["newsprint"], "17.3 4.5 3.2": ["boycotts"], "6.3 -2.2 8.0": ["reintroduced"], "5.7 10.0 1.0": ["coups"], "1.2 0.8 5.9": ["stents"], "-6.0 14.0 29.2": ["forage"], "-1.5 9.7 6.2": ["overbought"], "5.3 18.4 8.3": ["facet"], "22.4 8.6 6.5": ["fireball"], "-4.4 45.2 8.3": ["aggressor"], "9.8 0.4 11.7": ["da"], "-2.3 11.0 11.2": ["rebalancing"], "4.5 -0.1 3.3": ["nipped"], "10.7 3.1 5.9": ["siphon"], "0.7 16.6 5.3": ["mutiny"], "10.8 15.0 17.4": ["mama"], "-2.3 6.8 11.6": ["queer"], "14.8 2.8 3.2": ["unnerved"], "-0.0 29.7 8.2": ["reactionary"], "22.4 12.2 26.9": ["undersea"], "5.0 18.6 4.5": ["alleys"], "7.5 2.2 7.2": ["tailspin"], "1.7 0.0 2.4": ["formalities"], "6.4 -2.1 4.4": ["mezzanine"], "4.9 2.9 4.3": ["ecommerce"], "17.5 -1.8 7.7": ["phenom"], "6.2 18.2 10.1": ["rationalize"], "2.0 10.6 3.8": ["untimely"], "4.5 13.1 12.6": ["mutually"], "12.2 19.6 1.8": ["apocalyptic"], "2.7 9.5 2.9": ["denominated"], "4.3 2.0 9.8": ["sidebar"], "8.5 0.1 7.6": ["carriages"], "6.5 8.2 2.5": ["intermittently"], "3.0 2.3 3.3": ["curtailing"], "8.4 7.6 -2.1": ["layouts"], "-2.6 10.2 3.7": ["sparingly"], "-2.9 9.4 7.1": ["aggravate"], "2.9 14.2 -0.6": ["distinguishing"], "7.4 10.3 9.0": ["collectible"], "7.3 15.0 10.0": ["slog"], "15.0 -0.8 11.3": ["petite"], "-9.5 11.5 9.2": ["improvisation"], "24.3 6.9 20.2": ["prehistoric"], "-1.3 17.9 9.9": ["ballistic"], "-8.5 4.6 3.8": ["rehabbing"], "6.2 5.4 12.2": ["collars"], "2.8 7.1 10.2": ["muddled"], "-4.9 6.9 -5.7": ["enlightening"], "5.7 11.9 18.6": ["flora"], "2.7 9.1 2.4": ["admirably"], "13.5 6.0 9.7": ["dour"], "-10.2 9.2 1.6": ["treys"], "-0.5 14.7 -1.8": ["refraining"], "0.7 -3.6 8.3": ["vials"], "5.8 6.1 -1.9": ["furnishing"], "-2.6 4.6 1.1": ["sec"], "0.5 -1.3 10.8": ["endowments"], "11.6 10.8 3.4": ["foreground"], "-1.5 5.3 0.7": ["headmaster"], "4.9 1.4 8.4": ["lighthearted"], "2.3 18.1 8.9": ["republicans"], "3.2 3.0 9.3": ["vi"], "6.5 -6.5 3.4": ["coinciding"], "-5.5 10.3 6.6": ["powertrain"], "7.0 8.1 7.5": ["ambient"], "6.0 3.0 -4.2": ["consigned"], "2.0 11.3 1.4": ["linkages"], "7.9 -0.8 10.9": ["hinged"], "19.6 -4.1 13.3": ["scuttled"], "7.3 7.4 10.6": ["vomit"], "15.4 8.5 6.4": ["blueprints"], "2.7 2.8 9.6": ["banjo"], "17.0 8.6 6.7": ["inflating"], "10.1 14.3 1.3": ["proclaims"], "-2.3 5.1 7.2": ["homebuilder"], "5.4 4.3 4.4": ["jaunt"], "2.8 16.0 5.3": ["illogical"], "3.6 14.4 6.4": ["imaginations"], "14.1 4.7 12.1": ["pallets"], "8.4 11.1 13.3": ["northward"], "1.0 15.7 0.8": ["renounce"], "-10.5 10.9 3.7": ["attainment"], "6.9 -0.2 4.8": ["locomotives"], "21.4 5.0 6.1": ["implosion"], "12.4 3.4 12.3": ["parlor"], "10.5 -4.1 7.7": ["glitz"], "-4.0 -4.1 7.8": ["townhouses"], "-3.7 30.0 0.8": ["betray"], "11.2 10.9 7.4": ["wielded"], "-0.1 19.0 9.3": ["yells"], "7.7 15.3 1.0": ["eastward"], "12.9 21.2 8.5": ["obliterated"], "3.0 11.5 -0.3": ["conclusively"], "-3.6 10.1 1.7": ["inequalities"], "12.4 6.3 5.3": ["outlays"], "6.3 18.6 7.6": ["dagger", "compatriotic"], "15.1 20.2 3.2": ["naysayers"], "-3.5 8.4 -1.4": ["admonished"], "10.3 15.3 10.6": ["fragment"], "6.0 14.9 6.8": ["excruciating"], "0.8 11.8 21.6": ["flowering"], "8.7 1.9 4.7": ["kinks"], "-6.6 7.8 -2.2": ["facilitation"], "6.2 8.0 -3.7": ["unsurpassed"], "13.0 6.8 2.5": ["masterminding"], "-8.8 11.6 0.5": ["intellectually"], "11.8 4.4 6.4": ["bungled"], "5.1 18.1 -2.5": ["incendiary"], "7.3 7.9 7.6": ["amputated"], "2.0 12.9 4.7": ["protege"], "0.1 5.7 6.6": ["overworked"], "5.1 2.6 13.6": ["hippie"], "4.2 -0.6 7.3": ["legalizing"], "8.5 15.6 4.8": ["hitherto"], "4.4 3.5 5.2": ["dissipated"], "5.0 14.5 4.1": ["deploys"], "5.4 6.2 11.0": ["subpar"], "-2.3 10.5 -1.3": ["preaches"], "8.4 6.9 14.9": ["cub", "vesture"], "7.7 8.6 9.4": ["bottling"], "-12.1 9.6 2.3": ["rehearse"], "5.6 7.1 9.1": ["hustling"], "-5.6 7.2 4.9": ["fluoride"], "-2.9 1.8 1.9": ["saxophone"], "-1.4 15.9 2.9": ["unconditionally"], "3.3 -3.1 5.3": ["hairdresser"], "-5.7 1.8 0.0": ["autopsies"], "4.5 7.7 34.8": ["olives"], "5.6 6.3 13.7": ["scrapes"], "9.5 2.5 1.7": ["lounges"], "11.7 33.2 23.4": ["destroyer"], "4.8 4.6 3.4": ["carefree"], "4.5 10.4 3.1": ["honing"], "4.3 -0.6 8.2": ["accordion"], "-0.9 17.1 6.7": ["manipulative"], "15.0 0.0 0.9": ["dazzled"], "2.6 9.1 8.8": ["uncharacteristically"], "1.9 -2.3 -1.4": ["derailment"], "14.5 2.3 3.1": ["tester"], "0.3 3.3 8.0": ["turnpike"], "7.1 8.4 15.3": ["pimp"], "15.0 7.6 20.6": ["cones"], "-0.6 -3.4 12.8": ["cookbooks"], "7.7 3.1 9.9": ["washer"], "4.0 19.1 -0.4": ["intercepting"], "4.8 -1.4 -4.3": ["paperless"], "5.3 7.3 1.4": ["procuring"], "4.1 14.7 12.5": ["hiker"], "27.0 7.8 33.4": ["jelly"], "18.2 13.9 10.6": ["grotesque"], "11.5 3.6 8.3": ["placate"], "-4.5 14.3 6.6": ["prioritizing"], "10.7 1.0 24.4": ["cork"], "2.8 12.2 17.7": ["espresso"], "7.5 8.2 40.4": ["delicacy"], "-7.6 0.5 7.1": ["transplantation"], "3.5 6.2 1.8": ["reserving"], "21.6 17.0 9.5": ["spaceship"], "10.8 2.9 10.7": ["mag"], "5.8 7.1 27.5": ["sailboat"], "-6.0 8.8 5.8": ["institutionalized"], "5.2 3.1 10.7": ["companionship"], "11.0 15.8 9.1": ["censors"], "9.9 10.5 9.0": ["godfather"], "12.2 21.8 2.9": ["mobs"], "4.3 -1.8 11.4": ["filler"], "5.7 7.7 6.2": ["physiology"], "18.0 25.8 10.4": ["ferocity"], "-7.3 -1.5 -0.7": ["ensembles"], "1.7 5.6 7.4": ["expressway"], "13.5 11.9 4.2": ["enormity"], "15.9 7.7 3.4": ["stoking"], "4.6 3.1 12.2": ["spacewalks"], "16.1 8.8 0.0": ["emits"], "0.8 4.6 7.4": ["virtualized"], "-1.3 3.5 21.4": ["plantings"], "-3.1 4.3 6.0": ["melodrama"], "12.6 12.3 6.3": ["sever"], "8.5 5.1 3.2": ["clipping"], "2.4 8.0 7.5": ["transformers"], "0.9 8.2 29.5": ["hens"], "0.9 21.5 3.6": ["resourceful"], "7.1 4.1 0.3": ["fracas"], "7.6 8.7 5.7": ["ceded"], "-0.1 14.4 7.7": ["undeclared"], "-0.6 8.8 16.9": ["dayers"], "-3.6 -1.1 21.9": ["seasoning"], "-2.2 10.7 13.7": ["dengue"], "-2.2 -0.3 10.5": ["busing"], "12.8 7.4 6.5": ["alluring"], "1.3 12.2 4.0": ["firewalls"], "9.7 1.2 7.6": ["truckloads"], "9.6 3.8 1.1": ["taskforce"], "-6.2 12.7 -3.4": ["unprofessional"], "21.1 6.6 1.9": ["zoomed"], "7.3 3.9 12.4": ["takeaways"], "3.2 3.6 2.4": ["classed"], "21.8 3.3 1.9": ["toting"], "5.3 11.4 15.4": ["campfire"], "-2.3 15.1 5.3": ["flushing"], "12.3 6.6 0.5": ["commemorates"], "17.0 6.9 10.5": ["maestro"], "4.9 13.0 4.7": ["obstructed"], "3.0 0.3 0.4": ["airbags"], "13.3 18.7 1.4": ["defiantly"], "7.2 8.8 5.9": ["freaked"], "3.1 6.3 7.0": ["headliners"], "3.6 2.1 2.8": ["fitter"], "-7.9 0.3 5.7": ["disbursement"], "5.6 -5.1 -3.7": ["previewed"], "4.2 7.1 7.4": ["replayed"], "8.1 7.1 2.5": ["stockpiling"], "11.3 13.6 8.9": ["millimeter"], "10.6 11.0 4.3": ["smarts"], "-3.4 11.5 2.6": ["miscommunication"], "-7.1 1.4 17.8": ["teas"], "4.4 5.6 -4.3": ["romped"], "-1.1 5.5 3.6": ["amenable"], "3.8 3.6 4.9": ["crackdowns"], "6.3 7.1 5.7": ["haves"], "-5.4 5.3 3.5": ["tutelage"], "10.3 5.4 7.9": ["emptying"], "5.0 8.8 32.5": ["hen"], "-3.2 3.6 6.6": ["retraining"], "-1.5 10.4 3.4": ["reuniting"], "15.0 3.4 2.1": ["befitting"], "13.2 14.2 7.6": ["fraudsters"], "1.7 6.5 -6.0": ["expeditiously"], "3.4 14.4 11.3": ["ethic"], "13.4 13.4 11.5": ["clones"], "-3.3 6.0 18.6": ["tequila"], "-2.3 3.0 14.8": ["redemptions"], "10.6 2.5 8.6": ["suitably"], "9.0 1.3 10.5": ["manic"], "6.0 7.8 13.0": ["gorge", "recloser"], "9.4 -3.3 5.2": ["hoopla"], "3.3 7.5 13.3": ["basins"], "-6.4 0.8 1.6": ["origination", "challeged"], "10.0 5.4 9.0": ["graphs"], "-9.6 12.1 4.5": ["orthodox"], "-1.5 -4.4 -1.9": ["multidisciplinary"], "20.6 0.2 11.9": ["bulging"], "17.1 16.3 4.5": ["alphabet"], "15.9 22.7 9.6": ["superheroes"], "8.8 11.0 8.8": ["wrought"], "12.5 20.6 11.5": ["sneaky"], "1.4 6.2 1.7": ["squandering"], "8.1 11.6 10.1": ["mommy"], "4.4 12.1 11.0": ["hues"], "14.0 -1.8 0.3": ["manger"], "16.5 25.9 14.7": ["beings"], "6.2 9.7 9.6": ["circuitry", "surefire"], "9.3 -0.8 2.1": ["vogue"], "5.8 11.1 0.2": ["saver"], "8.0 11.6 11.3": ["lovingly"], "6.9 4.8 5.4": ["illustrator"], "9.6 12.0 14.8": ["healthiest"], "4.9 7.1 5.5": ["tooling"], "-0.0 16.8 -1.5": ["gunfight"], "9.5 6.0 3.1": ["din"], "15.9 4.0 18.3": ["greasy"], "7.3 6.0 10.7": ["spreadsheets"], "9.3 16.1 12.4": ["devastate"], "0.9 12.0 2.8": ["individuality"], "15.5 12.5 16.3": ["eyeballs"], "-7.7 11.4 7.9": ["wavelength"], "14.0 7.0 16.8": ["peeling"], "10.5 14.5 17.8": ["scatter"], "7.7 0.1 5.5": ["federations"], "5.3 6.9 9.1": ["transistors"], "5.5 7.4 6.7": ["gaffer"], "4.8 7.4 14.9": ["curing"], "4.8 1.3 -0.3": ["tm"], "7.1 10.9 2.6": ["pinpointed"], "1.9 -4.4 -5.9": ["helpline"], "11.2 10.7 13.3": ["whips"], "10.6 -0.1 6.2": ["hiccup"], "19.8 3.8 9.9": ["scuttle"], "7.9 13.4 13.6": ["moody"], "-5.4 2.7 -6.3": ["substantiated"], "-3.9 6.1 16.3": ["motherboard"], "2.3 1.2 9.6": ["sew"], "4.2 9.9 8.1": ["relished"], "-4.6 13.3 8.7": ["vocation"], "25.3 8.6 17.8": ["hairy"], "4.4 15.7 8.2": ["impeding"], "22.1 14.9 4.5": ["rudimentary"], "7.4 9.0 6.2": ["ll"], "-3.2 24.5 10.7": ["radioed"], "13.9 11.9 12.1": ["bliss"], "1.0 17.0 3.0": ["exaggerate"], "-5.0 2.0 7.2": ["statins"], "-6.0 5.9 -1.9": ["distinguishes"], "14.3 4.6 13.3": ["wheeling"], "9.9 5.9 21.2": ["lavender"], "5.2 41.4 0.7": ["jihadists"], "10.6 4.8 1.8": ["zipped"], "11.6 17.1 3.2": ["bloodbath"], "3.5 9.5 15.8": ["expeditions"], "17.4 30.0 9.9": ["humankind"], "17.1 14.8 19.2": ["pods"], "16.2 4.9 9.4": ["sculpted"], "4.9 8.2 4.7": ["multitasking"], "8.4 10.3 1.3": ["electrocuted"], "7.5 6.3 10.4": ["ratchet"], "5.5 19.3 0.8": ["illiteracy"], "-1.0 11.8 6.2": ["austere"], "2.2 8.9 -1.8": ["preachers"], "10.5 12.9 0.3": ["directional"], "6.2 11.1 2.8": ["potentials"], "18.5 13.6 6.6": ["hooded"], "1.6 3.9 -2.6": ["rejoining"], "2.1 11.6 1.9": ["arid"], "10.8 19.2 1.2": ["vilified"], "12.9 9.1 7.6": ["smacks"], "3.2 8.2 -0.4": ["eighty"], "-5.0 10.5 9.8": ["cinematography", "drinker"], "4.4 6.9 14.6": ["axle"], "7.7 11.0 -1.4": ["hilltop"], "5.5 4.9 7.8": ["semifinalists"], "5.1 6.1 4.0": ["interconnection"], "3.8 10.0 13.5": ["shutters"], "1.4 4.7 5.4": ["bowel"], "-3.2 1.0 22.8": ["kayaking"], "4.8 8.2 7.7": ["recessionary"], "8.5 9.6 7.8": ["reappear"], "11.5 1.2 16.2": ["mummy"], "4.9 2.8 5.6": ["nontraditional"], "3.5 -0.4 1.6": ["polymers"], "-5.1 -1.7 0.8": ["deferral"], "-6.2 12.0 4.5": ["goalscorer"], "8.3 19.1 8.3": ["vector"], "-4.0 4.1 6.7": ["summarize"], "7.2 6.0 4.8": ["tuneup"], "26.5 15.5 17.6": ["flailing"], "-5.4 17.8 1.7": ["avoidable"], "7.3 14.4 7.7": ["whine"], "0.1 15.8 -2.6": ["purposeful"], "8.9 1.9 10.2": ["coaxed"], "-0.7 1.2 8.9": ["puberty"], "7.7 5.5 0.5": ["scrawled"], "-11.3 -3.4 -1.7": ["reappointed"], "2.9 12.1 6.6": ["unsavory"], "4.8 31.3 3.8": ["totalitarian"], "8.4 -2.2 4.0": ["grappled"], "3.0 2.0 3.4": ["swingman"], "10.3 5.2 17.9": ["sumptuous"], "10.4 11.5 6.7": ["heaps", "lsu"], "2.4 5.6 2.2": ["aggregated"], "1.0 26.8 -5.5": ["atrocity"], "19.4 8.6 4.9": ["decapitated"], "0.5 18.7 3.5": ["inseparable"], "19.1 9.8 12.3": ["crates"], "9.7 19.5 11.0": ["hopelessly"], "5.0 -0.4 -0.2": ["reclassified"], "-2.1 16.2 13.1": ["sarcasm"], "2.5 12.6 8.0": ["patching"], "5.4 23.8 13.5": ["sanctuaries"], "3.5 12.8 10.5": ["hunch"], "9.1 -1.2 7.7": ["freebies"], "2.1 5.2 0.5": ["earner"], "10.0 3.6 5.2": ["multiplex"], "7.2 5.2 14.5": ["accompaniment"], "14.8 13.0 22.8": ["cape"], "8.6 9.3 -0.9": ["unheralded"], "-2.8 3.8 10.2": ["undercard"], "6.9 12.6 -0.1": ["harshest"], "17.5 4.3 0.3": ["buzzed"], "4.2 7.6 1.9": ["jogged"], "2.1 9.1 4.8": ["oblige"], "-3.0 7.0 3.5": ["elects"], "6.3 2.8 4.4": ["falsifying"], "4.5 13.5 9.6": ["physicality"], "-6.3 2.7 13.8": ["dispensaries"], "-3.4 3.1 -0.9": ["inhibitors"], "6.0 4.3 14.2": ["abnormally"], "15.5 12.1 17.7": ["lava"], "9.5 20.0 3.8": ["scrolling"], "-7.2 11.4 13.5": ["aquifer"], "7.1 1.7 7.1": ["payoffs"], "4.6 -2.4 2.8": ["straightened"], "8.0 8.3 8.3": ["depress"], "8.5 2.5 0.7": ["rev"], "43.3 11.7 8.4": ["titans"], "15.3 5.5 15.5": ["snare"], "6.8 1.3 10.6": ["dunked"], "12.1 9.4 15.3": ["gusto"], "2.7 4.6 16.2": ["sugarcane"], "14.3 10.2 3.9": ["dizzy"], "-6.2 11.7 45.3": ["walleye"], "5.8 29.8 -0.0": ["jihadist"], "2.0 15.7 -0.4": ["blasphemy"], "6.6 4.0 2.1": ["permissions"], "-4.8 -4.2 2.9": ["adjudged"], "0.5 6.1 16.5": ["medicinal", "miembros"], "5.2 8.4 10.2": ["intro"], "17.3 20.4 24.6": ["claws"], "11.9 4.1 14.1": ["trucker"], "22.7 6.8 3.8": ["erecting"], "12.1 0.1 1.9": ["renews"], "8.4 20.7 5.0": ["idiotic"], "4.0 13.2 1.0": ["transgressions"], "5.2 10.8 1.4": ["anointed"], "-0.9 7.8 10.7": ["wagers"], "15.8 -0.1 0.1": ["checkered"], "4.6 4.5 9.7": ["inactivity"], "8.6 -4.4 2.8": ["yoy"], "11.2 -5.1 12.2": ["crimp"], "7.9 8.5 3.7": ["impersonating"], "-0.8 11.4 14.9": ["tailgating"], "-1.8 13.9 19.3": ["orchards"], "-8.6 10.5 2.8": ["cognizant"], "18.6 3.6 10.0": ["moribund"], "12.3 13.6 4.3": ["desolate"], "-3.8 3.4 0.4": ["amplifiers"], "16.4 7.8 7.5": ["rumbling"], "7.5 15.5 10.8": ["shopkeeper"], "-1.7 18.0 8.2": ["heals"], "9.3 4.6 4.9": ["relented"], "6.5 1.1 2.7": ["dawned"], "18.9 14.2 17.7": ["snowball"], "7.3 22.4 5.3": ["cancerous"], "8.8 14.9 6.7": ["mystique"], "1.9 16.5 3.9": ["charted"], "20.0 5.3 11.3": ["flotation"], "5.7 0.6 -0.8": ["plaudits"], "15.7 16.8 11.5": ["gleefully"], "8.6 -1.4 6.0": ["mil"], "13.9 10.1 -3.4": ["blaring"], "3.7 7.7 1.1": ["consummated"], "6.9 16.9 3.4": ["cleanse"], "14.1 0.9 7.2": ["tanked"], "7.5 6.3 8.1": ["sultry"], "2.0 9.4 19.3": ["gin"], "14.0 12.6 10.3": ["hammers"], "-1.7 4.8 10.0": ["sweatshirt"], "14.9 14.7 7.3": ["thunderous"], "6.1 3.1 22.2": ["restaurateur"], "4.4 13.8 9.7": ["muse"], "3.2 9.1 17.1": ["firecrackers"], "13.0 6.0 7.0": ["junkie"], "19.2 7.8 12.5": ["emblematic"], "-5.2 0.6 -1.7": ["sociologist"], "-3.5 1.5 3.7": ["auditioning"], "5.8 0.5 6.6": ["threaded"], "7.1 9.5 7.3": ["squatters"], "6.8 10.1 12.5": ["unpredictability"], "-0.2 16.5 3.4": ["dishonesty"], "6.2 8.7 -0.7": ["subjecting"], "20.9 2.8 5.2": ["mimics"], "13.1 10.6 8.7": ["overgrown"], "17.9 1.0 14.4": ["scooping"], "5.3 12.1 15.3": ["molds"], "0.0 18.4 9.8": ["unproductive"], "2.1 4.7 -2.4": ["depositions"], "1.1 -0.4 8.6": ["resurface"], "2.9 16.0 2.9": ["worshiped"], "16.6 1.1 9.0": ["janitor"], "5.4 8.1 14.8": ["grills"], "2.8 1.5 6.8": ["collarbone"], "17.0 8.3 9.1": ["overhang"], "-3.9 25.8 6.4": ["provocations"], "12.9 5.5 6.1": ["shredding"], "2.9 7.1 15.6": ["snooker"], "16.8 2.9 5.8": ["grandiose"], "14.3 4.6 7.9": ["hovers"], "-4.7 3.1 11.0": ["quotations"], "12.3 10.8 23.7": ["kite"], "7.7 18.8 7.7": ["silos"], "-2.9 2.0 6.5": ["immunizations"], "3.9 15.8 10.0": ["stoic"], "12.5 18.6 3.6": ["stares"], "6.9 6.5 6.9": ["stockpiled"], "-6.1 6.1 1.9": ["neurologist"], "8.9 21.9 1.8": ["virulent"], "7.0 3.9 -0.2": ["enthralled"], "15.1 -0.3 14.0": ["nylon"], "7.5 5.0 -0.1": ["belting"], "2.5 10.7 5.4": ["impeded"], "0.6 10.9 0.9": ["analytic", "sideeffects"], "-2.6 2.8 0.0": ["personable"], "5.1 8.1 7.0": ["reparations"], "-5.0 8.9 10.4": ["learner"], "2.5 3.2 9.1": ["dries"], "3.6 6.2 40.5": ["mango"], "15.9 10.1 -4.6": ["vanguard"], "4.1 19.4 10.1": ["colonialism"], "22.5 6.2 7.3": ["cavernous"], "22.5 12.1 -1.6": ["reborn"], "10.4 4.8 0.2": ["breathless"], "11.1 16.2 5.5": ["traverse"], "0.5 3.5 -0.8": ["financings"], "-6.4 12.6 2.1": ["approachable"], "10.0 8.3 9.9": ["shrugs"], "12.8 9.2 10.1": ["thermometer"], "-6.2 6.9 18.9": ["snowmobiles"], "-3.3 -0.4 6.5": ["sterilization"], "0.4 -0.0 1.6": ["rector"], "8.5 9.0 17.4": ["trolling"], "10.7 7.5 23.2": ["porcelain"], "4.8 1.5 -1.9": ["vented"], "7.8 21.6 6.3": ["dares"], "7.4 12.0 3.1": ["strident"], "-1.3 3.8 5.6": ["biomarkers"], "10.5 8.9 8.1": ["painstakingly"], "4.9 0.5 3.2": ["clincher"], "4.2 9.6 6.3": ["hardening"], "16.5 6.3 12.4": ["bathed"], "14.1 8.5 5.2": ["shameless"], "8.7 7.8 11.7": ["breweries"], "2.5 -8.4 1.7": ["ironed"], "4.6 6.7 4.6": ["veer"], "11.9 16.6 0.7": ["farthest"], "0.7 4.6 9.8": ["pocketbook"], "3.7 2.0 3.1": ["neuroscience"], "7.0 10.3 15.7": ["brittle"], "4.9 -2.1 7.4": ["carpeting"], "8.2 1.7 6.2": ["cords"], "20.5 8.6 9.7": ["mimicking"], "2.6 15.4 9.3": ["rendezvous"], "9.3 21.4 20.1": ["mole"], "16.1 10.6 5.5": ["propping"], "2.8 4.2 10.5": ["nuptials"], "13.4 39.2 4.9": ["tyrant"], "4.4 1.9 0.8": ["unscheduled"], "7.0 6.0 10.8": ["gong"], "16.3 -0.9 5.3": ["fronting"], "13.9 10.4 13.7": ["vanishing"], "2.1 3.8 8.6": ["consternation"], "6.1 7.9 5.2": ["regularity"], "3.9 8.8 9.6": ["gore"], "12.4 12.1 1.5": ["viewable"], "6.1 12.0 8.9": ["radioactivity"], "15.3 -0.8 7.0": ["roiled"], "1.9 1.0 7.0": ["aggregates"], "11.0 3.1 32.7": ["pearl"], "2.8 7.2 -1.5": ["purification"], "3.1 12.8 5.6": ["inscription"], "4.6 4.6 2.7": ["coped"], "-3.6 3.6 4.0": ["bettered"], "5.7 13.8 18.3": ["breakers"], "9.7 3.3 2.4": ["ratcheted"], "-0.8 1.9 9.9": ["dyed"], "-4.2 2.6 -1.6": ["lectured"], "7.1 9.2 22.2": ["pyrotechnics"], "8.4 9.7 7.3": ["slit"], "17.6 6.6 27.5": ["panda"], "5.4 14.5 1.7": ["instantaneous"], "9.3 15.1 2.4": ["modernity"], "18.3 9.1 21.5": ["kangaroo"], "10.2 9.0 11.0": ["walled"], "4.7 10.0 0.3": ["taint"], "16.5 4.0 20.4": ["cracker"], "7.6 9.4 3.3": ["seeping"], "8.1 16.8 14.8": ["peasant"], "14.9 15.3 5.5": ["spied"], "3.5 2.2 21.9": ["bun"], "-6.3 -2.7 -4.4": ["orally"], "12.1 7.3 3.8": ["sizing"], "1.4 8.7 6.2": ["squaring"], "14.8 3.3 8.7": ["splashing"], "0.6 19.0 3.5": ["homophobia"], "2.6 10.0 2.6": ["sobbed"], "-2.3 1.5 13.7": ["bridal"], "5.5 3.1 10.5": ["holdup"], "6.8 11.3 8.5": ["strangle"], "3.0 18.5 9.5": ["calculus"], "-3.9 1.6 1.9": ["unsupervised"], "7.1 6.2 -5.1": ["commemorated"], "4.7 12.6 6.8": ["fooling"], "7.6 1.9 7.3": ["coupling"], "19.4 14.7 4.7": ["horizontally"], "12.6 21.0 7.2": ["ducking"], "-5.8 14.2 1.5": ["chaplains"], "6.0 10.4 24.4": ["springtime"], "-4.2 -1.2 3.3": ["curators"], "-1.8 7.6 10.6": ["chagrin"], "14.1 -3.6 7.0": ["spiraled"], "17.8 8.8 1.4": ["malfunctioning"], "9.4 3.8 12.8": ["mansions", "zug"], "3.7 11.7 5.5": ["affectionate"], "-1.0 16.0 2.7": ["comprehension"], "-0.5 4.2 -4.2": ["pertains"], "0.6 13.8 1.3": ["harbored"], "-0.9 0.9 11.7": ["fingernails"], "-2.5 8.9 4.2": ["abatement"], "0.6 -3.5 1.9": ["refinanced"], "-1.4 6.3 8.4": ["retroactively"], "12.3 9.4 4.0": ["marketplaces"], "5.1 -4.4 2.4": ["haircuts"], "16.9 7.6 14.8": ["crate"], "-0.5 7.4 30.7": ["flavorful"], "5.4 10.1 13.0": ["foggy"], "5.2 6.2 9.8": ["hangout"], "7.9 1.1 3.3": ["boulevard"], "12.8 10.9 6.9": ["smeared"], "7.5 5.6 7.4": ["interspersed"], "-10.8 5.6 12.1": ["substitutions"], "3.0 6.5 19.2": ["smokes"], "0.0 9.9 5.6": ["opportune"], "7.0 12.9 15.0": ["diseased"], "-5.6 -1.8 5.6": ["credential"], "2.8 5.9 -0.9": ["lifetimes"], "6.6 8.8 11.8": ["newlyweds"], "20.5 8.9 9.2": ["bulge"], "6.2 7.3 0.7": ["equated"], "6.6 11.4 14.8": ["dunes"], "13.2 8.1 13.7": ["camels"], "8.0 26.9 -1.7": ["fanatical"], "11.8 0.1 -0.6": ["interestingly"], "8.2 9.0 10.9": ["consequent"], "-6.4 12.2 6.0": ["instructs"], "2.8 1.9 -1.7": ["researches"], "-0.8 8.7 2.5": ["phoning"], "20.0 4.8 7.9": ["leaky"], "7.8 7.8 8.3": ["revel"], "1.0 -2.1 2.5": ["amiss"], "7.8 13.3 3.7": ["enlightenment"], "-3.7 5.9 5.7": ["goalkeeping"], "2.2 -1.4 0.7": ["logjam"], "4.2 9.4 8.2": ["moaning"], "0.7 6.9 4.1": ["mingling"], "1.0 5.1 8.1": ["substituting"], "6.0 8.4 13.9": ["alpine"], "-2.1 1.9 2.8": ["correlate"], "-8.5 2.3 -2.4": ["edits"], "17.5 2.1 5.2": ["atrium"], "14.0 7.0 6.6": ["sprawled"], "16.7 20.3 -2.2": ["frontiers"], "-0.9 7.9 -2.1": ["instructive"], "7.3 16.6 12.0": ["loathe"], "-2.7 2.3 10.5": ["vitro"], "7.4 22.7 4.3": ["whispering"], "17.5 5.4 -0.4": ["glorified"], "-3.9 6.3 4.9": ["remarried"], "27.7 2.8 -0.4": ["writedown"], "-8.8 8.5 7.1": ["seatbelt"], "1.9 -7.4 9.9": ["di"], "9.6 13.7 -0.4": ["confiscate"], "22.9 10.3 7.2": ["symbolized"], "3.7 3.7 11.8": ["urbanization"], "5.0 14.2 3.7": ["ceases"], "5.0 12.3 3.8": ["insistent"], "7.5 3.2 6.3": ["redo"], "-0.6 6.9 8.4": ["eliminations"], "-9.0 10.1 1.3": ["deviation"], "9.1 11.5 7.0": ["disintegration"], "-0.5 7.1 4.9": ["parochial"], "13.3 -3.5 0.5": ["furore"], "7.5 12.5 11.6": ["palaces"], "12.7 10.6 6.2": ["perfecting"], "-4.6 11.3 16.2": ["backcountry"], "16.1 5.5 0.8": ["christened"], "14.5 9.4 3.5": ["clearest"], "-0.1 12.7 12.7": ["lyric"], "9.8 14.7 8.6": ["fireman"], "-0.0 4.1 5.5": ["dormitories"], "13.8 31.2 0.8": ["repel"], "-3.0 8.9 2.2": ["playlist"], "5.1 0.7 14.3": ["peat"], "6.4 1.1 1.0": ["mainline"], "12.9 0.9 9.5": ["enclosures"], "13.9 4.1 14.8": ["confetti"], "8.2 2.8 8.1": ["capex"], "4.3 1.3 11.0": ["harp"], "1.5 12.5 4.6": ["interferes"], "7.0 9.3 2.1": ["jubilation"], "0.6 2.1 -1.2": ["rectified"], "16.2 6.7 7.5": ["hoisting"], "5.8 8.6 3.5": ["confessing"], "22.0 22.6 22.9": ["slug"], "8.3 11.7 5.7": ["doubtless"], "6.9 6.1 7.2": ["adhesive"], "9.9 9.9 11.4": ["cools"], "-6.1 10.0 1.8": ["cerebral"], "7.5 -4.2 -5.2": ["toiletries"], "-2.0 -0.6 9.7": ["anecdotal"], "11.3 -2.9 2.9": ["assuage"], "-3.0 2.9 3.2": ["metallurgical"], "29.0 15.2 6.0": ["flaming"], "30.9 -1.0 21.4": ["jumbo"], "-2.0 3.4 1.4": ["fragrances"], "-3.8 8.6 4.1": ["scoresheet"], "-9.3 2.0 9.3": ["paroled"], "9.9 9.8 8.3": ["trunks"], "2.9 15.7 2.8": ["diffuse"], "3.6 12.0 3.5": ["apologetic"], "6.6 11.0 9.6": ["lunged"], "9.5 5.3 14.2": ["dusting"], "8.2 5.5 19.9": ["tailed"], "8.1 -1.0 10.8": ["bodied"], "9.3 6.0 4.8": ["dissolving"], "12.5 2.3 7.2": ["tatters"], "0.1 15.4 4.9": ["fakes"], "6.8 3.9 6.9": ["tinker"], "6.0 17.5 0.3": ["uncontrollable"], "1.7 6.7 1.4": ["amass"], "0.7 4.9 0.7": ["entitle"], "-3.1 -3.5 2.7": ["microfinance"], "23.4 11.9 12.3": ["windmills"], "17.1 16.9 7.5": ["blinking"], "8.7 2.7 2.5": ["funneling"], "3.2 13.6 5.0": ["boyhood"], "11.0 3.5 6.4": ["basking"], "1.8 -0.6 19.7": ["phosphate"], "5.6 9.2 7.2": ["lessening"], "8.0 5.4 -2.0": ["acrimonious"], "1.4 1.6 10.1": ["datacenter"], "5.9 2.4 7.9": ["depositing"], "9.3 13.0 -1.2": ["furthest"], "9.9 6.5 0.4": ["dynamism"], "9.4 4.1 -2.4": ["overdrive"], "7.0 12.2 18.2": ["polar"], "11.5 3.4 5.4": ["installer"], "5.4 10.5 1.9": ["anthems"], "2.2 27.5 4.9": ["despised"], "19.1 3.5 16.6": ["rainforest"], "-1.9 11.6 1.0": ["abrasive"], "0.1 17.3 6.5": ["skillful"], "0.3 3.2 5.9": ["harmonized"], "8.5 5.6 0.6": ["physicists"], "7.1 -1.1 5.5": ["raunchy"], "12.3 9.0 5.2": ["wrenching"], "11.1 5.4 1.7": ["vaults"], "0.0 11.3 6.4": ["fractions"], "-7.2 4.8 0.4": ["apprised"], "-0.5 5.1 9.5": ["baritone"], "7.4 -2.2 7.3": ["scrubbed"], "-6.8 16.7 0.3": ["candidly"], "8.5 5.6 6.4": ["grasped"], "6.8 1.3 11.5": ["clubbed"], "18.7 7.6 6.4": ["tethered"], "-3.2 11.3 14.9": ["shotguns"], "-2.0 3.1 5.6": ["uniformity"], "11.1 19.4 9.8": ["selves"], "-6.1 14.7 5.2": ["impeach"], "20.2 17.3 24.0": ["sucker"], "4.9 10.8 10.4": ["relishes"], "3.0 13.6 4.7": ["gripe"], "5.8 12.6 22.1": ["flocks"], "-1.8 18.4 11.5": ["sowing"], "1.4 3.5 3.6": ["ethically"], "-4.1 0.6 10.2": ["probate"], "-0.5 0.6 -1.2": ["orphanages"], "15.2 8.5 14.8": ["beauties"], "3.2 42.4 3.6": ["traitors"], "6.3 13.5 7.8": ["regenerate"], "4.9 23.5 26.5": ["poachers"], "3.1 16.0 4.0": ["interchangeable"], "12.4 3.7 2.5": ["springing"], "2.2 -3.5 1.1": ["resold"], "1.4 10.1 5.9": ["bandmates"], "15.1 22.3 15.8": ["plunder"], "1.6 3.0 23.7": ["pups"], "-0.1 -5.6 1.4": ["sabbatical"], "1.2 10.3 2.2": ["newsworthy"], "-2.5 1.8 0.2": ["signee"], "4.3 4.6 5.2": ["astounded"], "-6.4 11.6 -2.3": ["condoned"], "3.8 7.1 10.3": ["grille"], "3.4 12.3 6.0": ["swears"], "6.3 10.2 2.3": ["douse"], "4.9 19.8 13.4": ["villager"], "8.8 10.1 4.9": ["stoning"], "0.6 6.5 8.1": ["indulgence"], "-2.6 7.9 8.2": ["parliaments"], "-7.9 0.7 2.8": ["adjourn"], "12.9 4.7 2.1": ["reinvented"], "11.6 9.9 14.3": ["grumpy"], "9.3 9.2 -1.2": ["unconfirmed"], "2.0 26.9 9.0": ["indiscriminately"], "11.1 9.6 1.7": ["integrator"], "12.1 16.3 1.9": ["deafening"], "5.4 5.2 26.6": ["oats"], "-5.4 -0.8 0.5": ["educates"], "0.5 9.0 9.3": ["mortuary"], "4.6 8.6 12.9": ["royals"], "10.5 1.9 28.1": ["takeout"], "15.2 1.3 4.4": ["ditching"], "18.5 21.6 26.3": ["beetles"], "6.3 3.9 7.6": ["rupiah"], "2.2 2.8 -1.2": ["aligns"], "8.3 10.2 12.3": ["cavity"], "0.5 20.7 10.6": ["unspoken"], "-0.6 6.7 3.2": ["characterizes"], "20.0 12.0 9.9": ["motif"], "3.4 -3.8 6.9": ["fetuses"], "9.0 3.1 16.5": ["acrylic"], "-5.1 17.3 6.9": ["scripture"], "15.4 8.4 28.6": ["oily"], "3.6 7.8 12.5": ["riff"], "6.1 3.8 10.0": ["auspicious"], "8.7 9.7 6.6": ["vapor"], "2.7 -0.5 -0.4": ["devotes"], "4.3 3.5 21.6": ["seasonally"], "18.7 11.8 29.3": ["rodent"], "14.3 11.8 10.4": ["passersby"], "15.2 4.3 5.4": ["punctured"], "16.4 13.0 13.3": ["pitiful"], "3.4 10.5 5.6": ["quandary"], "-4.9 3.1 2.0": ["investigational"], "-7.3 0.6 8.4": ["itineraries"], "14.8 7.3 9.2": ["cushions"], "10.9 -1.7 1.0": ["le"], "3.1 -0.4 2.7": ["gastrointestinal"], "15.7 3.8 12.9": ["microchip"], "2.3 7.0 9.1": ["pews"], "0.9 4.8 9.2": ["culvert"], "12.3 9.7 6.6": ["drip"], "2.0 10.3 17.9": ["rhyme"], "-3.3 10.8 10.3": ["pelvis"], "11.5 3.7 1.1": ["strode"], "4.1 29.7 8.2": ["garrison"], "2.9 11.4 9.7": ["peacemaking", "capello"], "14.4 3.0 9.0": ["blossoming"], "-3.1 1.6 12.4": ["mammogram"], "-4.9 1.1 -5.9": ["counsels"], "11.2 2.1 7.9": ["grandmothers"], "-1.0 0.9 1.5": ["premiering"], "11.3 11.7 4.1": ["absorbs"], "18.4 12.6 4.8": ["howling"], "6.9 -0.0 11.3": ["reintroduce"], "14.8 15.3 6.4": ["innumerable"], "8.5 13.5 4.4": ["inadvertent"], "18.6 7.6 6.2": ["stylized"], "13.9 7.7 8.2": ["fused"], "-4.7 -1.7 7.1": ["reconvene"], "11.2 19.4 9.5": ["crook"], "3.6 9.1 -0.9": ["misrepresentation"], "4.7 8.6 5.7": ["indignation", "thermodynamic"], "2.8 18.7 1.3": ["ilk"], "-3.4 5.9 -0.5": ["assigns"], "19.2 8.2 7.1": ["curiously"], "-1.8 -0.0 -0.4": ["practicality"], "20.8 1.5 9.3": ["drugmakers"], "9.5 7.8 21.5": ["waiters"], "4.0 2.5 9.3": ["coronation"], "-0.3 2.6 2.1": ["diversions"], "15.4 12.5 6.2": ["hitman"], "18.8 18.1 32.2": ["owl"], "15.9 5.2 5.8": ["weathering"], "13.7 1.5 3.3": ["coughed"], "5.8 4.7 1.8": ["defused"], "9.3 0.1 10.9": ["pouch"], "10.2 5.4 4.5": ["yesteryear"], "10.8 8.5 0.6": ["toil"], "2.1 4.8 9.3": ["mused"], "8.2 4.4 -1.6": ["rumblings"], "12.4 1.9 7.0": ["exuberance"], "12.1 8.6 7.0": ["caricatures"], "6.0 1.6 9.8": ["apprentices"], "4.7 -1.5 3.9": ["gated"], "7.7 3.4 8.9": ["physique"], "0.2 8.3 -6.0": ["veracity"], "15.8 11.9 6.6": ["scammers"], "18.8 6.0 5.5": ["moguls"], "14.3 13.5 24.6": ["ketchup"], "16.9 5.7 0.9": ["disposals"], "8.5 8.5 8.2": ["gash"], "11.8 15.6 12.5": ["frosty"], "-9.4 2.8 -3.8": ["corroborated"], "7.9 0.9 2.9": ["respectability"], "20.9 4.8 14.0": ["floundering"], "7.1 29.8 2.2": ["terrorize"], "1.4 14.7 -1.5": ["demeaning"], "16.2 9.5 3.3": ["leapfrog"], "4.9 7.1 16.6": ["baker"], "-0.6 17.8 0.6": ["altitudes"], "13.9 13.9 9.5": ["grandpa"], "-4.6 -0.3 12.5": ["tanning"], "2.8 3.1 10.8": ["cutback"], "11.2 -1.1 6.3": ["stockbroker"], "7.9 12.5 21.6": ["fauna"], "9.2 6.3 9.8": ["cranky"], "8.3 10.0 9.1": ["gallop"], "8.3 -8.8 5.3": ["mull"], "1.7 -5.2 2.4": ["transcription"], "8.0 -0.6 -0.0": ["consumables"], "2.1 13.6 2.1": ["disorganized"], "6.1 16.6 2.7": ["beholden"], "13.3 8.8 9.1": ["excitedly"], "3.4 9.4 3.0": ["overcomes"], "0.3 10.0 7.2": ["boyfriends"], "11.0 11.6 1.7": ["keypad"], "-6.6 6.7 -1.0": ["specificity"], "3.1 8.3 13.1": ["riffs"], "7.7 12.3 -1.0": ["abducting"], "5.7 8.2 5.2": ["breakeven"], "4.3 3.1 5.6": ["bristled"], "10.8 2.9 25.6": ["pandas"], "6.5 16.6 9.6": ["townspeople"], "0.5 4.5 17.7": ["watercolor"], "-1.3 5.8 7.0": ["furnaces"], "14.5 17.4 8.5": ["blinding"], "9.5 12.9 5.6": ["spenders"], "6.9 17.0 4.0": ["posse"], "12.2 14.5 2.2": ["unnerving"], "-2.0 13.9 16.9": ["denuclearization"], "17.3 0.0 9.9": ["muscled"], "3.4 12.3 -1.3": ["outclassed"], "10.5 -4.6 7.5": ["centering"], "9.8 12.0 7.4": ["intestines", "nonoperating"], "-2.5 7.0 9.1": ["thyroid"], "13.7 11.9 8.6": ["pronged"], "9.8 16.5 7.1": ["thwarting"], "3.0 5.8 1.6": ["computational"], "6.3 2.4 3.3": ["riled"], "8.8 7.5 4.4": ["bandages"], "2.1 3.7 10.8": ["lupus"], "12.0 4.8 4.7": ["sapped"], "3.9 9.0 7.6": ["mutate"], "-0.7 10.8 5.9": ["inhibitor"], "5.6 11.1 4.0": ["galvanize"], "3.8 8.7 12.6": ["decommissioning"], "10.2 1.3 11.6": ["stuttering"], "0.6 2.0 12.9": ["mt"], "15.7 10.9 7.1": ["graces"], "16.2 6.1 6.5": ["replicas"], "16.4 10.2 1.2": ["immortalized"], "2.8 8.2 9.4": ["ambiance", "mesons"], "2.2 8.1 16.3": ["snowstorms"], "9.2 5.7 4.5": ["courtrooms"], "5.4 2.3 18.2": ["sod"], "10.3 13.5 3.8": ["unflattering"], "-0.6 30.2 14.0": ["ammo"], "9.6 3.4 7.9": ["airy"], "4.0 5.6 0.8": ["laudable"], "10.4 8.7 7.6": ["lol"], "3.4 19.9 4.6": ["abuser"], "1.8 8.8 5.2": ["executes"], "13.8 16.4 14.7": ["playfully"], "-1.1 6.9 4.4": ["infrequent"], "17.9 15.5 1.3": ["inferno"], "15.4 10.9 32.5": ["reptile"], "6.9 3.2 5.2": ["exhibitor"], "7.9 15.5 10.1": ["paralyzing"], "-1.0 8.6 6.6": ["abort"], "-2.0 20.7 5.7": ["dereliction"], "-6.5 -5.3 7.9": ["salons"], "1.0 9.3 5.8": ["interplay"], "1.5 11.9 7.0": ["sensual"], "-4.1 6.1 11.1": ["glaucoma"], "15.7 12.2 7.6": ["miraculously"], "-4.5 6.1 6.2": ["epidemiology"], "0.5 4.2 5.0": ["cuff"], "14.8 11.9 9.9": ["harbinger"], "-8.0 1.5 6.6": ["continuance"], "13.0 0.8 0.5": ["ushering"], "6.8 5.5 1.4": ["laundering"], "-2.9 8.9 2.9": ["categorize"], "-1.2 11.8 2.9": ["discharging"], "-4.0 11.1 11.7": ["bettors"], "6.1 4.2 -3.5": ["pacemaker"], "8.8 3.2 2.1": ["genesis"], "2.2 15.3 5.9": ["feminism"], "16.4 -4.3 5.5": ["weighty"], "6.6 4.6 13.2": ["canteen"], "-0.2 10.3 1.3": ["manifested"], "3.0 -0.3 10.9": ["tiebreaking"], "9.6 4.6 14.9": ["truckload"], "7.8 10.1 0.8": ["vehemently"], "5.4 0.2 12.0": ["splurge"], "-2.1 7.7 4.3": ["compiles"], "7.9 13.7 3.3": ["averse"], "0.5 2.4 5.1": ["minivans"], "13.6 1.1 9.2": ["pales"], "3.9 -2.4 5.1": ["invalidated"], "7.3 13.2 17.9": ["roasting"], "-0.2 21.6 2.9": ["intolerant"], "-2.3 21.4 3.4": ["persevere"], "7.0 -2.2 -4.3": ["centenary"], "14.9 16.5 13.8": ["heavenly"], "3.4 16.0 7.8": ["tribals"], "9.4 16.3 4.2": ["countryman"], "0.4 11.5 7.8": ["worldly"], "-0.6 6.1 0.1": ["discourages"], "14.0 8.7 2.1": ["sexiest"], "7.1 27.1 5.2": ["miscreants"], "-6.4 13.7 5.7": ["sectionals"], "-3.7 8.2 13.5": ["neutered"], "5.2 9.9 8.1": ["blustery"], "5.1 9.6 22.8": ["pup"], "4.3 39.1 4.8": ["battlefields"], "6.7 5.4 3.6": ["ferrying"], "4.0 10.6 -1.0": ["synchronize"], "1.8 8.1 -2.4": ["diagnosing"], "18.9 2.9 -0.4": ["pacts"], "7.5 10.4 5.1": ["industrialists"], "10.3 10.6 5.7": ["grossing"], "9.1 3.1 6.7": ["siphoning"], "-1.5 3.1 7.9": ["elevations"], "5.6 10.8 9.5": ["serenity"], "-2.4 21.0 11.0": ["nuance"], "7.2 1.0 11.6": ["temp"], "3.4 -1.1 1.2": ["afoul"], "0.4 22.4 6.8": ["diplomatically"], "4.1 8.9 0.6": ["freer"], "-5.2 11.3 9.1": ["radiotherapy"], "-1.4 12.0 6.5": ["timetables"], "4.4 6.7 -1.3": ["fainted"], "-5.5 31.9 4.1": ["valor"], "0.4 11.0 4.9": ["loitering"], "8.9 -1.9 7.4": ["fretting"], "-6.0 3.3 4.1": ["anthology"], "11.6 27.6 8.3": ["outlaws"], "9.7 1.2 3.6": ["el"], "-3.8 6.8 15.6": ["stallion", "harper"], "2.4 12.7 13.3": ["pothole"], "10.2 21.5 6.1": ["germ"], "-0.0 17.1 7.7": ["lymphoma"], "7.3 28.4 9.0": ["immortal"], "10.2 4.1 8.8": ["bemused"], "2.4 40.5 3.6": ["coward"], "8.8 22.7 18.9": ["infestation"], "16.6 11.9 13.3": ["glide"], "4.4 1.6 5.3": ["televise"], "2.9 1.1 10.3": ["embroidery", "nonmonetary"], "8.2 7.0 2.5": ["sordid"], "3.5 9.0 8.4": ["piecemeal"], "2.9 2.4 5.7": ["webpage"], "4.1 22.4 -2.8": ["valiant"], "5.5 13.6 3.6": ["groupings"], "5.7 8.5 4.8": ["transmitters"], "17.8 11.9 3.5": ["roars"], "-4.0 5.6 2.7": ["volleyed"], "-0.9 14.7 3.3": ["prays"], "0.6 1.7 6.9": ["thematic"], "15.5 7.1 15.5": ["pallet"], "9.0 6.7 1.3": ["agitating"], "6.2 1.6 3.8": ["sidestepped"], "13.9 9.9 11.5": ["arcane"], "6.5 9.8 21.6": ["vase"], "3.4 5.5 0.1": ["overuse"], "10.5 15.7 8.2": ["flashlights"], "7.3 5.4 14.8": ["candies"], "-2.2 17.3 6.2": ["prequel"], "3.1 13.8 8.6": ["itch"], "9.4 6.1 8.4": ["fixation"], "18.1 5.9 14.1": ["fluorescent"], "8.6 10.8 10.6": ["hyun"], "15.0 12.4 10.8": ["unsightly"], "9.4 6.5 5.9": ["undiscovered", "sonofusion"], "1.1 1.9 10.1": ["miffed"], "20.9 11.7 5.3": ["catapult"], "5.1 12.3 -0.1": ["wrongful"], "11.5 5.5 4.6": ["displacing"], "2.0 2.6 -2.7": ["envisage"], "25.1 0.3 21.1": ["chunky"], "-1.1 -4.9 4.5": ["supervises"], "18.2 14.8 9.6": ["axes"], "4.1 6.5 7.7": ["disjointed"], "0.3 -3.2 6.0": ["milled"], "13.8 5.7 7.1": ["drab"], "10.7 10.6 11.2": ["gratuitous"], "5.6 6.7 8.1": ["prohibitions"], "4.4 11.0 5.5": ["retina"], "0.4 1.1 37.3": ["blueberries"], "7.1 14.8 10.7": ["sundown"], "3.2 -0.9 5.4": ["condensed"], "17.8 12.0 0.0": ["harnessed"], "-3.1 9.8 10.5": ["vaccinate"], "8.1 15.0 10.8": ["hyperbole"], "-3.2 4.8 0.7": ["unpublished"], "-4.0 1.8 8.6": ["ligament"], "7.8 13.5 1.8": ["gauging"], "-2.9 8.8 14.1": ["dialect"], "12.0 8.4 9.5": ["canyons"], "8.4 18.8 9.9": ["levers"], "2.9 3.3 -3.7": ["validating"], "31.0 3.6 -3.9": ["heiress"], "10.4 7.4 19.5": ["concoction"], "-1.3 15.2 5.1": ["biases"], "-0.6 10.4 4.9": ["likeable"], "1.5 11.0 0.2": ["leaflet"], "4.9 1.5 -0.9": ["clearinghouse"], "15.9 3.3 -4.2": ["rebranding"], "6.6 3.1 3.3": ["aerobics"], "2.0 2.2 2.5": ["biochemistry"], "-0.9 6.2 11.0": ["dieting"], "-6.4 4.9 21.3": ["breads"], "0.7 12.8 2.3": ["strangulation"], "11.6 23.1 11.9": ["warring"], "4.8 20.1 0.5": ["blurring"], "-8.2 0.4 3.8": ["midwives"], "5.2 -0.6 0.2": ["focussing"], "2.4 -0.8 7.5": ["nutritionist"], "1.3 15.7 5.2": ["latent"], "-7.9 4.8 13.0": ["interbank"], "10.8 9.3 5.3": ["darted"], "14.5 8.9 18.3": ["queens"], "14.6 7.7 9.8": ["pluck"], "2.2 3.5 6.5": ["bandage"], "10.7 23.4 2.2": ["taunts"], "4.6 4.4 9.4": ["frayed"], "8.9 6.1 -7.4": ["divestitures"], "0.4 12.4 -2.8": ["bestseller"], "5.5 8.6 1.0": ["literate"], "13.0 13.3 30.6": ["larvae"], "1.7 0.7 3.0": ["sanctioning"], "0.7 3.6 3.5": ["burnout"], "11.8 0.2 6.5": ["tightens"], "2.6 14.5 6.5": ["psychotic"], "12.6 13.3 4.1": ["equipments"], "2.1 11.1 9.8": ["algebra"], "8.1 15.2 6.7": ["imagines"], "6.3 7.9 7.5": ["gaffes"], "15.0 14.9 3.0": ["rages"], "0.6 13.6 5.9": ["persevered"], "-2.2 13.7 10.4": ["guesses"], "2.8 9.6 29.4": ["entree"], "2.3 1.4 4.4": ["toolkit"], "21.5 14.9 13.3": ["hive"], "8.9 2.5 15.8": ["slaughterhouse"], "8.1 13.7 5.1": ["ringleader"], "0.5 3.9 -1.6": ["rezone"], "8.6 19.6 6.5": ["atom"], "10.4 8.8 4.1": ["conjured"], "-3.4 3.9 9.4": ["filers"], "6.3 5.6 9.7": ["lorries"], "8.1 20.6 5.8": ["atheists"], "19.7 5.0 4.3": ["enveloped"], "11.0 14.6 7.9": ["sprays"], "0.1 5.8 11.5": ["psoriasis"], "7.4 17.1 4.2": ["wrongfully"], "2.8 5.0 4.4": ["shafts"], "16.0 5.1 10.3": ["shrugging"], "8.5 -1.1 8.7": ["formaldehyde"], "-4.3 6.3 8.9": ["divorces"], "0.7 1.8 9.5": ["loggerheads"], "4.1 1.4 8.4": ["precede"], "19.8 23.7 13.0": ["bandit"], "11.9 1.8 20.4": ["velvet"], "20.7 14.1 8.6": ["tilting"], "-1.5 1.1 5.4": ["dentistry"], "3.7 7.0 13.1": ["caretakers"], "17.8 19.3 4.8": ["withering"], "3.2 9.7 -4.1": ["unsubstantiated"], "4.2 9.5 3.0": ["tribulations"], "7.5 14.1 7.2": ["triage"], "8.5 10.0 8.6": ["stitch"], "1.6 11.2 7.1": ["segmentation"], "-4.7 1.8 13.1": ["couture"], "-3.3 5.0 1.2": ["surety"], "3.3 4.5 15.7": ["tights"], "3.2 12.0 1.5": ["avionics"], "7.1 6.1 5.3": ["besting"], "-3.6 6.4 13.7": ["chronically"], "12.3 5.1 14.4": ["electro"], "11.9 0.8 1.6": ["erupting"], "8.3 11.9 9.9": ["whims"], "14.4 3.2 5.0": ["shelving"], "-11.1 10.6 4.4": ["intercourse"], "12.3 6.5 1.5": ["ricocheted"], "13.9 4.9 12.7": ["swatted"], "9.8 18.7 9.1": ["maneuvered"], "4.1 3.5 -3.8": ["publicizing"], "17.8 9.6 9.8": ["encyclopedia"], "13.4 18.2 11.2": ["witches"], "-2.1 11.0 4.7": ["amputation"], "19.3 3.1 6.9": ["readies"], "10.3 11.1 -6.1": ["technologically"], "9.7 5.5 6.1": ["privatizing"], "-2.3 14.1 11.7": ["gambler"], "19.0 4.9 10.2": ["slashes"], "19.0 14.5 11.2": ["expanse"], "5.3 9.7 15.6": ["substrate"], "19.1 8.9 59.5": ["squid"], "5.6 -0.3 1.9": ["transitioned"], "8.1 11.9 15.5": ["huts"], "2.0 42.3 4.5": ["comrade"], "2.1 8.7 7.4": ["headers"], "12.4 13.6 5.4": ["globalized"], "11.7 0.7 5.5": ["ponders"], "-0.8 -5.7 3.4": ["uncapped"], "12.1 19.3 6.7": ["stylus"], "9.3 9.5 9.1": ["enclaves"], "4.2 3.0 25.8": ["silt"], "1.4 12.5 5.0": ["shrines"], "1.0 8.8 6.8": ["drunkenness"], "20.3 18.2 34.2": ["beetle"], "13.9 7.4 8.7": ["supercomputer"], "16.1 23.8 15.8": ["stalk"], "1.1 -3.3 1.4": ["benefitting"], "10.6 11.0 5.0": ["chute"], "5.1 0.9 8.6": ["bookkeeping"], "14.6 23.5 10.5": ["encroaching"], "-1.1 3.2 7.8": ["telecasts"], "0.8 4.8 1.1": ["playlists"], "-4.0 11.1 9.4": ["selectman"], "8.9 17.6 12.7": ["daybreak"], "0.6 3.7 10.0": ["nanometer"], "-2.0 7.4 6.5": ["nepotism"], "2.8 5.4 4.6": ["strikingly"], "4.1 0.2 5.4": ["supra"], "1.5 25.2 30.3": ["baits"], "8.8 2.4 0.1": ["bribed"], "-2.7 7.7 33.1": ["broth"], "-2.2 19.4 14.2": ["fielders"], "-0.4 0.9 6.3": ["hoteliers"], "5.3 10.1 11.0": ["fracturing"], "-2.8 7.2 2.8": ["renditions"], "10.3 18.8 11.9": ["ancestor"], "12.4 14.8 2.5": ["electrified"], "6.1 23.7 11.9": ["clans"], "-3.3 22.1 7.1": ["intuition"], "19.9 0.6 12.8": ["cheery"], "-3.3 11.3 -2.2": ["eulogy"], "-0.9 10.8 1.9": ["hymns"], "6.9 11.5 26.0": ["cougar"], "-3.1 8.0 41.8": ["steelhead"], "5.0 9.4 7.6": ["confiscation"], "-11.8 11.3 4.5": ["deviate"], "11.5 0.2 2.5": ["straddles"], "12.4 5.0 38.8": ["avocado"], "11.9 9.7 2.4": ["delisted"], "10.2 20.4 15.7": ["bacterium"], "6.8 8.6 9.8": ["subcontinent"], "-4.4 12.4 1.9": ["uninformed"], "4.9 11.6 -2.2": ["loudspeaker"], "-1.6 3.2 0.1": ["defibrillator"], "0.1 4.6 1.5": ["pardons"], "-9.5 8.8 1.0": ["recollections"], "-4.4 3.1 12.6": ["jewelers"], "-5.4 22.4 3.7": ["demoralized"], "7.5 7.4 7.6": ["spurts"], "4.3 11.6 0.8": ["aptitude"], "11.9 2.3 0.3": ["brokering"], "14.6 25.0 24.2": ["spear"], "14.9 4.0 11.0": ["midget"], "-4.4 10.1 0.8": ["bereaved"], "14.0 9.7 8.6": ["uber"], "3.1 17.1 -0.6": ["spoilers"], "14.8 14.0 4.6": ["contours"], "-5.2 14.8 -1.3": ["reciting"], "3.0 8.0 3.1": ["ferried"], "5.9 3.5 10.9": ["decreed"], "4.2 5.2 8.4": ["legitimize"], "-5.0 3.3 2.8": ["summarizes"], "-2.0 14.1 10.6": ["colds"], "12.7 20.6 4.8": ["massed"], "4.4 7.2 5.7": ["penitentiary"], "5.5 21.7 4.9": ["flanks"], "1.3 13.7 2.2": ["impediments"], "10.3 15.2 9.7": ["wink"], "12.7 5.2 10.7": ["elastic"], "-7.2 6.7 7.7": ["absenteeism"], "2.3 4.6 4.6": ["conclave"], "22.0 9.6 12.0": ["mascots"], "7.0 17.8 -2.0": ["showering"], "9.5 8.5 5.5": ["environs"], "2.4 -5.5 7.0": ["firming"], "13.0 -0.7 5.7": ["downsized"], "5.5 4.0 -3.2": ["reaffirming"], "-0.6 24.0 5.8": ["worldview"], "16.4 11.3 6.0": ["replicating"], "6.1 8.9 9.1": ["bunches"], "-1.6 5.9 13.1": ["aunts"], "5.0 12.3 13.5": ["brooding"], "14.2 6.2 14.5": ["splendor"], "3.8 -0.4 6.3": ["skits"], "13.0 11.3 5.2": ["dud"], "14.0 8.6 15.5": ["steelmakers"], "8.0 11.5 5.9": ["slugging"], "0.5 10.9 0.0": ["amenity"], "2.8 8.7 2.7": ["electrodes"], "10.5 13.3 4.3": ["awaken"], "-2.5 13.7 2.9": ["prejudiced"], "15.5 16.0 8.2": ["freaks"], "0.9 3.1 7.5": ["bobbled"], "-2.8 1.5 2.9": ["remorseful"], "5.1 3.8 5.9": ["enforces"], "3.3 12.5 16.3": ["hairs"], "6.9 7.8 3.2": ["venting"], "8.4 15.8 6.4": ["fortitude"], "-6.7 0.6 4.8": ["fiduciary"], "9.0 4.4 11.0": ["shouldered"], "-4.0 18.1 6.5": ["retorted"], "4.7 1.1 -2.5": ["interacts"], "6.2 -0.1 6.5": ["rapped"], "0.2 33.2 12.6": ["militaries"], "0.2 7.5 3.0": ["totality"], "5.3 1.1 3.8": ["weaves"], "1.2 10.1 3.8": ["thoroughfare"], "12.5 3.7 18.8": ["appetites"], "14.1 9.7 8.5": ["streaked"], "-0.5 10.0 10.5": ["quips"], "4.5 4.6 16.7": ["devolved"], "-0.6 5.1 8.3": ["serum"], "5.9 6.5 3.9": ["shadowed"], "7.4 10.1 2.8": ["jinx"], "-0.9 5.5 15.1": ["bitumen"], "-1.4 11.0 8.8": ["thermostat"], "16.8 8.8 6.8": ["scurrying"], "2.1 8.5 -0.6": ["terse"], "7.9 6.3 9.0": ["gasping"], "-3.7 0.0 10.6": ["contraceptives"], "-0.4 3.4 -0.2": ["crediting"], "2.0 13.2 5.9": ["reconciling"], "8.0 -0.5 1.7": ["bolsters"], "-8.7 -0.9 2.3": ["semesters"], "6.8 11.8 2.3": ["grinned"], "6.7 2.0 15.2": ["sprinkling"], "7.5 5.7 7.6": ["composites"], "7.4 12.3 -2.1": ["mourns"], "8.3 17.1 3.9": ["underestimating"], "19.9 6.7 5.5": ["unwieldy"], "-5.8 5.3 9.2": ["funnier"], "3.9 -2.8 3.7": ["recouped"], "15.0 3.8 4.4": ["populate"], "1.7 10.9 4.0": ["migraines"], "2.0 6.6 12.6": ["sodas"], "4.1 -5.8 -0.6": ["annulled"], "28.5 12.4 18.8": ["cube"], "-4.3 18.1 -2.0": ["communicator"], "-2.0 5.4 10.6": ["bandh"], "1.4 3.6 3.3": ["heartwarming"], "5.9 9.1 7.7": ["overzealous"], "19.6 13.0 5.7": ["monopolies"], "5.1 10.1 5.4": ["pronouncement"], "4.4 15.4 6.3": ["dislikes"], "11.6 10.0 10.1": ["waterfalls", "mender"], "-0.8 15.9 7.3": ["flashback"], "25.6 7.2 14.9": ["hunk"], "1.8 13.4 7.5": ["shivering"], "16.7 2.7 11.2": ["scoops"], "1.5 24.5 3.8": ["racists"], "5.2 3.3 -3.3": ["consolidates"], "6.5 5.6 6.4": ["promos"], "1.6 -8.5 -1.1": ["accommodates"], "2.3 5.3 8.9": ["tidbits"], "9.1 -2.4 11.5": ["trims"], "14.1 4.3 16.9": ["rollers"], "8.9 13.6 9.2": ["smug"], "15.6 16.2 3.7": ["dislodge"], "26.3 3.5 16.1": ["outsized"], "16.0 4.7 14.0": ["woe"], "6.9 5.5 6.9": ["bookmarks"], "-3.6 7.2 -5.3": ["devout"], "10.5 6.8 3.5": ["localization"], "21.0 16.2 6.7": ["ghastly"], "-9.0 7.9 10.0": ["widowed"], "3.1 -1.3 3.3": ["siphoned"], "-0.4 18.1 11.3": ["uncooperative"], "0.5 7.7 8.0": ["surveyors"], "-0.6 14.0 5.1": ["scribe"], "-6.1 0.6 10.7": ["attribution"], "-6.5 -1.7 -1.1": ["biographical"], "-0.5 0.4 6.1": ["bemoaned"], "8.0 3.2 7.7": ["nicked"], "4.5 6.0 33.1": ["piers"], "-4.4 21.3 1.5": ["incapacitated"], "12.4 6.5 13.5": ["stomachs"], "15.4 11.1 19.3": ["feline"], "6.9 4.4 10.1": ["backhander"], "-6.7 -1.1 2.5": ["airfares"], "3.7 3.1 21.4": ["tart"], "2.5 2.8 36.4": ["cherries"], "11.3 9.1 3.4": ["turbo"], "0.4 -0.6 -7.7": ["shortness"], "7.2 -0.1 8.1": ["pocketing"], "9.3 14.7 5.8": ["warped"], "-7.6 9.2 11.2": ["upperclassmen"], "10.0 8.2 9.8": ["tit"], "1.2 7.1 12.1": ["rapping"], "7.1 4.4 11.6": ["incinerator"], "6.0 14.7 19.3": ["artifact"], "20.0 4.3 12.5": ["fanciful"], "-0.2 1.9 1.4": ["sparred"], "7.4 -1.0 0.7": ["clamping"], "7.2 16.7 6.2": ["shorthand"], "-5.3 2.1 8.6": ["newscasts"], "-1.2 -1.3 8.2": ["osteoarthritis"], "11.7 15.6 16.6": ["cutters"], "-2.8 6.4 10.4": ["brothels"], "9.3 10.4 12.5": ["depictions"], "2.8 -3.0 6.9": ["bras"], "2.7 0.4 -1.0": ["tranches"], "4.2 7.8 10.4": ["disrupts"], "9.7 20.3 3.1": ["purposefully"], "0.8 13.2 -1.8": ["incriminating"], "-9.6 -1.6 16.3": ["semen"], "2.4 18.5 5.7": ["mow"], "8.5 13.7 1.0": ["reorganizing"], "7.4 6.8 7.4": ["refill"], "-2.8 24.2 -1.0": ["reprisal"], "14.3 13.6 11.8": ["fella"], "4.2 8.2 8.4": ["prolonging"], "-4.2 14.5 8.1": ["vehicular"], "6.1 9.2 11.9": ["ah"], "9.6 2.5 1.8": ["scrip"], "7.0 8.0 20.9": ["coarse"], "13.2 6.7 9.6": ["middlemen"], "8.6 5.8 64.6": ["clams"], "7.8 5.7 8.8": ["nullify"], "-7.4 3.5 8.9": ["bicycling"], "7.9 12.9 1.2": ["seduced"], "8.3 0.7 12.4": ["trucked"], "1.8 25.2 10.7": ["quests"], "1.5 -3.6 -0.2": ["reinstating"], "10.0 17.3 3.2": ["protectionist"], "10.7 11.5 7.4": ["aptly"], "9.7 -2.6 3.4": ["reselling"], "-7.1 11.0 9.7": ["baserunners"], "5.7 9.3 2.9": ["puncture"], "9.4 11.8 6.1": ["panacea"], "18.8 6.9 15.0": ["measly"], "7.2 9.7 10.7": ["rag"], "10.5 13.3 4.5": ["realms"], "-1.1 12.9 9.3": ["pragmatism"], "7.2 -5.9 0.6": ["renegotiated"], "12.5 6.7 1.2": ["hurriedly"], "3.4 5.8 -4.8": ["readable"], "10.5 17.0 6.3": ["inevitability"], "25.0 10.9 22.6": ["bunny"], "3.2 -1.1 1.0": ["roping"], "-15.2 -4.6 7.1": ["caseload"], "13.9 5.5 5.2": ["cranking"], "3.1 8.1 62.0": ["mussels"], "7.3 15.2 4.6": ["fates"], "-4.9 4.3 -1.7": ["neurology"], "0.5 1.5 0.3": ["rerouted"], "15.3 3.0 11.5": ["tacky"], "-4.0 11.2 2.8": ["geospatial"], "3.2 1.7 -0.5": ["underpaid"], "-2.7 15.8 5.7": ["idealism"], "17.2 2.2 2.9": ["branching"], "11.4 6.8 8.0": ["barreled"], "-3.1 0.0 8.4": ["bipolar"], "-0.8 5.5 2.1": ["complainants"], "1.7 30.5 1.6": ["partisans"], "2.2 9.7 1.3": ["videotaping"], "2.4 17.4 3.9": ["corrosive"], "-4.4 10.1 4.4": ["immunized"], "-9.7 1.0 1.1": ["coursework"], "-0.7 5.5 14.3": ["barangay"], "20.4 -1.7 9.2": ["carousel"], "6.5 26.7 6.2": ["despise"], "35.5 13.1 6.1": ["whiz"], "6.0 6.4 0.4": ["blacklisted"], "4.2 23.0 4.9": ["flatly"], "-1.0 -1.7 4.8": ["chiropractic"], "-1.2 3.6 11.7": ["parkway"], "3.1 7.0 7.7": ["subsystems"], "-3.4 6.2 2.1": ["promulgated"], "11.3 6.2 4.9": ["couches"], "9.9 3.5 9.5": ["embryonic"], "-0.7 4.8 10.3": ["agreeable"], "3.4 10.0 19.1": ["utensils"], "19.7 12.7 23.3": ["sunken"], "0.1 0.4 8.7": ["operas"], "10.4 7.3 2.8": ["ascended"], "-2.0 6.1 1.8": ["borrows"], "4.0 11.6 9.2": ["repurchases"], "-1.9 23.8 10.8": ["oftentimes"], "3.7 7.6 13.8": ["novices"], "3.1 1.8 6.8": ["pampered"], "6.5 3.7 8.1": ["granddaughters"], "7.3 11.9 -1.2": ["salutes"], "13.9 -4.1 -0.2": ["reignited"], "9.2 14.7 3.9": ["coolly"], "0.6 5.7 1.7": ["backstretch"], "16.4 18.1 34.3": ["crow"], "12.3 10.4 10.5": ["diagonal"], "-1.8 0.8 -1.1": ["impresses"], "7.5 16.2 3.6": ["tacklers"], "8.0 12.1 -4.3": ["blitzed"], "-3.9 0.5 0.8": ["headteacher"], "4.2 2.0 22.0": ["thoroughbred"], "5.9 6.7 3.9": ["configurable"], "6.9 18.4 -1.8": ["enabler"], "14.1 16.2 9.5": ["demonstrator"], "12.9 -1.9 4.1": ["lettering"], "-0.9 9.7 1.9": ["contexts"], "3.0 -0.1 8.0": ["bouquets"], "-2.4 16.1 1.0": ["dispatches"], "27.8 30.9 29.6": ["ant"], "-3.8 3.0 4.7": ["attributing"], "0.6 -3.1 -0.8": ["fulltime"], "10.0 3.9 0.5": ["downgrading"], "-0.5 5.5 9.5": ["potassium"], "6.4 -1.5 4.1": ["toughened"], "-0.1 -2.8 6.5": ["lockup"], "2.8 9.7 2.1": ["intersect"], "10.4 4.9 25.6": ["tacos"], "0.1 13.2 9.2": ["outlying"], "11.9 4.1 9.7": ["grainy"], "8.2 11.9 3.3": ["wailing"], "3.5 -1.6 11.1": ["maturation"], "1.2 5.4 3.2": ["naturalized"], "8.8 5.3 4.5": ["canisters"], "4.1 9.4 -1.6": ["cleanest"], "1.3 9.1 9.2": ["bicyclist"], "0.0 12.0 7.1": ["habitual"], "-4.2 8.7 13.9": ["septic"], "3.0 12.2 7.3": ["antioxidant"], "11.2 7.1 9.6": ["seething"], "-3.3 3.5 1.3": ["midwife"], "16.7 19.2 12.8": ["broom"], "4.8 14.2 5.5": ["landlocked"], "12.8 24.8 2.1": ["crusader"], "-9.2 17.4 -4.8": ["interrogate"], "3.4 17.6 5.7": ["blitzes"], "4.1 13.2 8.7": ["hospitable"], "1.0 1.3 6.9": ["acrimony"], "6.9 7.3 8.2": ["immaculate"], "10.9 8.7 10.6": ["purists"], "7.4 9.5 1.1": ["wrest"], "2.0 24.5 8.2": ["instinctive"], "4.8 6.6 17.4": ["cleats"], "11.1 13.1 5.3": ["trickery"], "-3.0 8.2 5.0": ["divergence"], "3.8 19.0 3.3": ["manifestations"], "-3.5 4.3 11.2": ["stopover"], "12.6 7.5 5.3": ["averting"], "18.9 6.4 8.4": ["industrywide"], "8.6 5.9 12.6": ["dreamy"], "3.9 12.8 12.4": ["ensue"], "-4.8 21.8 3.0": ["responder"], "-0.3 11.7 4.0": ["ecumenical"], "5.9 -1.8 -6.4": ["reneged"], "0.3 21.7 9.0": ["optimist"], "14.7 15.0 18.3": ["paws"], "-2.2 2.9 -0.2": ["methanol", "sidefooted"], "7.1 32.4 9.4": ["warlord"], "11.7 2.1 7.1": ["meandering"], "6.8 5.4 10.2": ["telemarketing"], "6.4 -1.3 11.9": ["bling"], "17.8 14.1 16.2": ["boulder"], "2.3 -3.2 15.7": ["necklaces"], "7.7 12.0 7.4": ["ascendancy"], "-3.2 12.0 2.7": ["critiques"], "-5.0 13.7 3.9": ["uneducated"], "7.3 10.1 8.4": ["fabricating"], "19.3 -3.4 -4.1": ["millionth"], "5.2 10.8 4.9": ["aftershock"], "11.2 0.2 0.6": ["controversially"], "2.6 24.9 1.9": ["neutralized"], "1.4 10.4 6.7": ["legacies"], "3.0 11.2 12.3": ["alarmingly"], "13.1 9.4 -0.4": ["annals"], "10.9 10.2 8.1": ["flops"], "-3.9 2.3 7.9": ["mammography"], "-1.4 10.0 2.8": ["plainclothes"], "-0.2 8.6 6.4": ["carbohydrate"], "-3.5 6.6 14.7": ["winemaker"], "8.6 18.8 2.6": ["reviled"], "11.2 9.7 13.3": ["sidestep", "mailman"], "13.9 2.4 4.4": ["handsomely"], "15.9 6.5 9.8": ["pegs"], "2.7 3.4 -2.4": ["compressor"], "12.8 7.4 7.5": ["slumber"], "16.6 3.1 9.2": ["anxiously"], "16.8 3.6 1.1": ["multipurpose"], "5.3 19.7 9.0": ["solitude"], "16.8 13.2 28.5": ["parrot"], "3.6 24.2 3.7": ["maimed"], "8.6 8.9 9.2": ["astronomer"], "3.5 19.9 9.7": ["impulses"], "9.7 5.2 -0.2": ["snuffed"], "3.7 2.0 6.2": ["meaningfully"], "23.5 4.2 13.2": ["shimmering"], "8.4 1.8 0.6": ["toiled"], "1.3 4.3 5.6": ["twelfth"], "7.2 5.8 5.4": ["unconcerned"], "-2.2 4.1 2.1": ["pediatricians"], "-5.9 8.1 17.3": ["antiquities"], "11.0 7.1 5.9": ["hum"], "4.6 0.5 8.0": ["technicality"], "4.4 6.8 22.2": ["snowboarders"], "-7.0 -2.0 17.3": ["recyclables"], "14.8 5.8 6.2": ["strangest"], "17.5 10.0 6.7": ["mesmerized"], "-0.1 24.1 3.3": ["demoralizing"], "4.5 9.8 14.1": ["dike"], "5.8 3.3 13.4": ["distillates"], "17.7 4.6 4.7": ["buffeted"], "17.2 12.1 26.6": ["jig"], "6.7 13.2 -3.2": ["outlast"], "-1.7 4.7 14.6": ["gavel"], "-2.9 1.1 7.0": ["tempers"], "15.5 17.9 0.9": ["scariest"], "4.2 8.2 4.2": ["babysitter"], "9.7 13.1 3.8": ["bumbling"], "1.0 13.4 6.2": ["sustains"], "5.2 2.7 31.7": ["crispy"], "5.1 -2.7 -0.4": ["appropriateness"], "3.9 -0.4 4.2": ["telethon"], "1.8 5.4 8.3": ["shorted"], "5.4 2.1 -1.2": ["functioned"], "14.0 3.0 6.7": ["grapples"], "0.5 -3.7 10.8": ["raves"], "1.0 0.8 13.3": ["granular"], "7.0 -3.3 1.5": ["reconsidering"], "2.1 1.9 7.0": ["skew"], "-3.4 7.6 13.1": ["homebuilding"], "2.1 1.6 8.0": ["zeroed"], "6.3 9.2 2.4": ["amplify"], "-4.9 16.4 13.3": ["narcotic"], "4.4 7.5 7.7": ["trekking"], "-7.1 17.3 4.3": ["inference"], "2.2 6.2 7.7": ["videoconferencing"], "1.4 -6.3 1.3": ["converters"], "3.0 14.1 7.8": ["barbs"], "1.1 3.2 6.6": ["motocross"], "3.3 2.7 5.6": ["skips", "handcart"], "14.7 9.2 6.0": ["niches"], "-4.3 5.4 9.0": ["vesting"], "2.9 1.7 8.0": ["uptown"], "6.2 2.6 17.2": ["carton"], "12.7 5.4 17.8": ["riverside"], "21.6 4.9 5.2": ["pulsating"], "1.7 3.9 2.6": ["installers"], "4.7 5.5 6.4": ["restarts"], "13.0 2.3 3.7": ["steeply"], "17.8 1.2 -1.5": ["imploded"], "15.0 4.3 9.8": ["gingerly"], "-2.7 2.1 4.3": ["caveats"], "7.3 5.5 12.8": ["drummers"], "-1.4 7.2 12.7": ["eyebrow"], "15.3 1.9 11.9": ["snags"], "-3.7 26.4 3.2": ["enmity"], "-6.8 1.3 3.2": ["rigor"], "0.8 15.5 0.5": ["inaudible"], "4.6 11.3 2.5": ["threesome"], "6.8 9.9 7.2": ["megapixel"], "14.7 11.2 0.5": ["reposition"], "-1.4 16.7 5.8": ["pleases"], "0.7 -2.8 13.8": ["looser"], "9.5 8.5 3.0": ["sleazy"], "13.1 12.7 5.0": ["fixated"], "18.6 10.8 8.7": ["flattening"], "-2.5 10.7 5.2": ["togetherness"], "6.0 2.2 2.8": ["looped"], "5.3 5.1 3.8": ["rigorously"], "12.2 12.8 34.0": ["alligators"], "1.3 1.8 0.8": ["uneventful"], "2.4 14.1 9.0": ["endures"], "-6.0 4.9 -1.0": ["valedictorian"], "5.0 7.3 6.5": ["perplexing"], "2.8 14.9 1.2": ["unambiguous"], "-9.0 8.8 7.2": ["appraisers"], "3.1 12.0 11.4": ["carbs"], "11.0 -5.1 -1.1": ["relaunched"], "11.2 2.4 19.2": ["turquoise"], "-6.5 9.8 1.4": ["texted"], "-5.4 1.4 2.7": ["delegated"], "7.3 -0.8 0.6": ["outgrown"], "3.8 11.0 3.9": ["longed"], "4.8 -0.6 12.8": ["stockings"], "9.0 21.2 15.7": ["slaughtering"], "9.1 6.0 7.7": ["unabated"], "9.5 4.2 5.4": ["spanking"], "2.6 6.7 -2.8": ["constituting"], "6.0 7.1 7.0": ["foolproof"], "-8.0 -2.7 -2.3": ["curated"], "-8.7 -2.0 2.8": ["sobriety"], "6.5 7.7 26.3": ["brood"], "-1.1 11.5 4.2": ["tolerable"], "1.8 14.4 2.0": ["precondition"], "8.0 5.7 5.9": ["prepping"], "10.9 12.0 7.9": ["hatchet"], "3.1 36.7 2.1": ["counterattack"], "1.6 7.0 7.0": ["chuckles"], "9.6 5.6 6.3": ["id"], "8.0 14.6 6.9": ["trespass"], "0.8 14.3 10.8": ["eluding"], "6.6 7.7 2.7": ["epitomized"], "2.9 24.8 3.8": ["liars"], "-6.6 7.7 3.3": ["determinations"], "1.2 8.3 8.5": ["gutters"], "13.0 1.2 6.0": ["drugstore"], "1.4 9.2 5.4": ["descriptive"], "-2.3 1.2 -4.3": ["exemplify"], "14.5 10.2 14.8": ["volcanoes"], "2.4 9.4 4.5": ["vibes"], "7.0 8.7 6.8": ["alters"], "9.2 8.2 -2.6": ["sensations"], "5.7 10.1 1.6": ["dejected"], "8.2 12.8 2.3": ["overture"], "7.3 2.2 4.4": ["ushers"], "18.6 15.1 -1.2": ["transnational"], "4.9 3.8 7.5": ["soundness"], "12.0 11.0 5.1": ["iteration"], "9.5 10.8 9.2": ["giggling"], "3.4 8.9 0.2": ["patted"], "2.8 8.6 4.2": ["redeeming"], "-1.2 3.6 16.7": ["earthy"], "1.5 -5.1 -3.5": ["hr"], "7.3 6.5 1.5": ["tipoff"], "-2.3 25.8 2.3": ["betraying"], "3.5 8.6 8.2": ["sharpness"], "16.5 13.8 9.5": ["chap"], "12.5 11.5 4.6": ["nightmarish"], "7.5 19.2 3.2": ["uncomfortably"], "-0.2 6.7 3.3": ["goalless"], "8.2 7.7 14.0": ["picnics"], "-2.4 21.2 4.8": ["redeployment"], "6.2 3.2 6.9": ["passcode"], "20.6 5.1 10.9": ["cascading"], "-2.1 2.5 4.3": ["normalize"], "5.4 0.7 5.9": ["genealogy"], "8.6 12.1 13.2": ["smacking"], "-0.5 6.7 24.3": ["almonds"], "7.9 8.3 14.6": ["tat"], "-0.3 5.3 13.7": ["plating"], "-4.0 9.2 -5.3": ["contradicting"], "-0.7 -0.6 7.3": ["lengthen"], "2.0 6.6 0.2": ["obtains"], "-1.5 2.6 4.2": ["heterogeneous"], "5.9 11.2 7.0": ["scents"], "9.6 -4.6 8.2": ["heaped"], "-4.1 8.5 2.4": ["sprain"], "4.6 12.8 -4.4": ["associating"], "3.0 4.3 56.0": ["sturgeon"], "19.4 19.9 13.7": ["mutant"], "17.5 -4.1 -1.4": ["advertises"], "1.1 13.1 12.8": ["acidic"], "7.1 7.3 21.7": ["greenery"], "2.9 19.9 -0.3": ["lawfully"], "10.0 18.7 4.7": ["clap"], "-6.3 -8.6 3.4": ["postgraduate"], "-9.4 12.2 3.3": ["hearsay"], "1.1 4.4 7.6": ["dislocation"], "12.5 15.7 18.8": ["stalks"], "0.1 13.5 4.1": ["susceptibility"], "9.4 13.2 23.1": ["blossoms"], "6.1 3.0 3.4": ["complementing"], "5.8 8.6 8.2": ["footpath"], "15.7 31.5 16.0": ["knight"], "8.4 8.1 8.8": ["quirks"], "9.3 8.9 7.4": ["speedster"], "13.0 3.3 29.0": ["meaty"], "9.1 11.3 4.0": ["behaves"], "4.1 2.5 6.9": ["fonts"], "-1.4 3.7 5.3": ["detours"], "12.4 9.3 8.0": ["linesman"], "9.4 5.2 0.6": ["reconfigured"], "0.6 -7.3 0.8": ["tel"], "5.6 -0.1 14.1": ["nuggets"], "-1.3 13.4 1.6": ["deterring"], "-1.7 9.4 2.6": ["culpable"], "-0.0 2.8 13.6": ["picky"], "7.8 6.5 8.9": ["beggars"], "11.0 1.6 8.8": ["leafy"], "9.2 20.7 11.5": ["navigational"], "-8.8 6.8 -6.5": ["admissible"], "-0.8 8.3 -2.2": ["counterparties"], "7.5 14.0 -0.7": ["confine"], "-12.3 4.5 5.1": ["autobiographical"], "0.2 13.5 4.4": ["feminists"], "10.6 8.8 7.2": ["dutifully"], "9.4 11.7 10.2": ["sharpening"], "11.7 17.2 10.8": ["multiplying"], "-7.8 5.7 3.0": ["hatchback"], "-4.8 23.3 6.0": ["winnable"], "12.8 2.7 0.8": ["mauling"], "9.0 2.3 10.7": ["agri"], "17.5 13.2 13.2": ["apes"], "15.6 5.7 15.3": ["accented"], "9.3 30.9 17.4": ["cannons"], "3.3 44.7 4.4": ["infidels"], "12.5 12.4 7.7": ["mule"], "2.8 8.9 2.3": ["hearse"], "-0.5 2.2 1.6": ["outgained"], "14.1 3.6 0.5": ["dampening"], "9.1 1.6 -0.1": ["feted"], "9.1 8.3 6.5": ["sauna"], "10.5 4.9 8.1": ["looping"], "6.9 11.4 10.1": ["unworkable"], "-7.7 6.7 -2.6": ["espoused"], "6.9 -6.1 11.9": ["silicone"], "-2.6 -1.3 4.2": ["panelist"], "6.8 6.8 7.7": ["fantastically"], "9.3 3.2 2.1": ["revved"], "-1.1 2.5 6.7": ["physio"], "3.4 1.7 11.3": ["handcrafted"], "16.9 3.6 -0.1": ["digitized"], "4.4 1.7 -4.2": ["redeveloped"], "7.7 3.7 18.1": ["lotteries"], "-4.4 8.4 9.3": ["familial"], "3.8 7.5 11.0": ["brewed"], "9.6 -0.4 1.6": ["orientated"], "4.4 13.1 2.1": ["woefully"], "18.1 3.5 14.4": ["lanterns"], "5.5 6.0 8.0": ["starch"], "14.9 9.7 6.9": ["clobbered"], "-5.7 6.7 0.3": ["angioplasty"], "1.6 2.4 7.9": ["parentheses"], "2.2 6.3 31.6": ["dredge"], "4.3 13.3 0.8": ["whistleblowers"], "-2.5 12.0 6.5": ["pips"], "0.2 3.2 0.6": ["overstepped"], "17.4 -2.0 29.6": ["plump"], "2.5 0.3 -5.1": ["exempts"], "1.0 0.8 11.4": ["mudslide"], "25.2 7.4 12.5": ["ringed"], "10.5 8.7 25.4": ["jigs"], "12.2 10.8 9.9": ["mercurial"], "-0.7 9.0 19.2": ["rowers"], "2.1 13.0 2.5": ["parameter"], "-1.4 7.2 5.4": ["divorcing"], "5.8 9.7 -2.1": ["chargers"], "8.5 6.7 -1.6": ["transmits"], "-0.5 10.8 36.9": ["waterfowl"], "11.8 16.5 14.5": ["melts"], "16.9 5.3 15.4": ["forklift"], "5.5 28.9 2.6": ["conspirators"], "-2.2 -10.7 -1.4": ["oversubscribed"], "9.0 0.4 5.6": ["abating"], "7.4 5.1 6.1": ["fireplaces"], "3.1 3.9 5.4": ["null"], "11.7 10.3 13.7": ["impossibly"], "12.7 7.4 7.4": ["signifying"], "3.5 12.3 7.7": ["sexism"], "0.8 -8.5 1.1": ["voided"], "13.0 15.3 4.9": ["whistling"], "10.7 10.4 5.1": ["tonic"], "-8.3 4.0 17.9": ["snowpack"], "-5.2 2.1 5.8": ["sire"], "8.9 9.0 7.7": ["razor"], "21.2 10.7 2.9": ["analogous"], "0.7 2.4 2.0": ["semifinalist"], "12.0 21.0 2.9": ["fiercest"], "2.9 21.0 5.8": ["troublemakers"], "10.3 4.5 18.1": ["sawed"], "10.7 5.6 1.4": ["unimpressive"], "4.6 5.9 12.2": ["streetcar"], "11.9 13.7 11.6": ["impotence"], "7.9 -0.4 3.3": ["reworking"], "3.7 3.7 6.3": ["penthouse"], "8.0 4.2 36.6": ["tofu"], "-0.3 17.1 4.5": ["anarchist"], "11.2 5.1 14.3": ["telly"], "-4.3 17.4 6.7": ["aloof"], "10.2 -1.6 12.4": ["swoon"], "6.1 4.1 13.7": ["bakeries"], "3.1 25.4 0.7": ["vigilante"], "-2.3 12.9 3.3": ["consequential"], "0.0 0.7 5.8": ["jailing"], "15.4 17.0 11.9": ["creeps"], "-1.4 7.7 -2.5": ["assessors"], "9.3 11.7 5.9": ["distasteful"], "4.4 -1.4 4.1": ["aggregating"], "3.3 12.6 8.8": ["computed"], "5.5 2.8 4.6": ["unearth"], "15.7 6.2 6.4": ["junkies"], "4.9 13.9 2.7": ["unusable"], "10.2 9.4 4.0": ["gust"], "7.3 4.3 0.7": ["structurally"], "-8.2 4.1 11.5": ["truancy"], "5.0 0.3 4.6": ["alleviating"], "4.6 -2.2 12.7": ["tapered"], "11.7 12.9 27.4": ["biscuit"], "-2.5 -1.8 4.4": ["convenes"], "4.7 -9.1 3.3": ["billings"], "1.1 15.4 2.7": ["frontal"], "6.8 8.1 2.0": ["dilutive"], "14.0 10.1 4.7": ["belatedly"], "3.7 -1.9 12.4": ["taper"], "-1.1 4.6 18.3": ["healthful"], "4.4 21.6 4.7": ["socialists"], "2.3 7.5 13.4": ["naturalist"], "15.2 0.1 3.5": ["tenfold"], "13.8 3.6 4.7": ["digested"], "5.6 31.8 7.3": ["nukes"], "-1.7 4.0 4.3": ["synopsis"], "2.9 10.9 22.5": ["feeders"], "1.1 7.1 3.2": ["repossessed"], "26.1 5.0 4.6": ["eponymous"], "4.6 1.6 0.3": ["groundswell"], "5.0 5.4 13.9": ["lakeside"], "-0.8 5.3 10.5": ["chromosome"], "-6.1 16.3 7.0": ["wiretap"], "7.1 -1.4 3.7": ["testimonial"], "4.6 6.4 3.3": ["deleting"], "1.8 12.0 5.7": ["disaffected"], "10.2 -0.5 -3.9": ["wooed"], "12.5 9.7 9.5": ["nonsensical"], "-1.3 10.2 19.0": ["brews"], "3.8 1.0 4.2": ["unfulfilled"], "8.2 14.4 2.5": ["smitten"], "13.1 9.7 15.7": ["boobs"], "14.1 5.0 2.7": ["reinventing"], "9.5 5.6 4.0": ["recreated"], "16.2 20.4 12.5": ["hubris"], "-2.7 -1.0 0.8": ["plenary"], "2.4 9.5 3.3": ["alternatively"], "2.2 14.5 7.6": ["sown"], "1.6 8.4 10.9": ["retracement"], "6.7 11.5 9.2": ["charade"], "10.3 2.1 9.7": ["magnesium"], "18.4 -2.1 7.1": ["sprouted"], "3.7 3.3 9.8": ["hampers"], "2.7 16.1 5.7": ["envious"], "7.6 25.7 13.2": ["unprovoked"], "9.6 10.3 3.6": ["flatter"], "5.2 11.4 11.4": ["craziness"], "13.4 9.3 9.6": ["grandstands"], "12.4 4.1 48.8": ["seaweed"], "32.3 6.1 11.7": ["dwarfs"], "16.4 7.8 9.7": ["listless"], "1.6 11.2 2.0": ["ambivalent"], "8.1 6.4 11.2": ["coil"], "2.1 9.4 15.4": ["rinse"], "5.1 6.5 5.8": ["widower"], "-2.2 11.4 15.1": ["judo"], "19.3 4.7 4.7": ["affixed"], "2.0 -1.9 17.2": ["carats"], "-1.8 2.1 -0.7": ["pertain"], "-6.1 -0.8 14.2": ["alumina"], "10.8 5.9 2.8": ["middleman"], "5.3 1.9 17.4": ["bistro"], "1.3 2.9 5.7": ["racially"], "5.3 20.0 5.2": ["kneeling"], "6.0 15.9 7.1": ["preoccupation"], "0.9 1.7 2.4": ["barged"], "5.1 13.2 0.8": ["mowed"], "-3.3 7.1 10.5": ["faculties"], "6.1 2.0 9.7": ["squabble"], "11.8 17.9 21.1": ["booty"], "6.1 0.7 5.2": ["interpretive"], "-6.5 -5.3 1.1": ["trimester"], "3.9 6.2 13.6": ["zest"], "1.4 6.8 5.3": ["prudence"], "-1.2 7.4 -0.9": ["scripting"], "4.0 11.0 2.1": ["inhibiting"], "1.9 18.6 2.3": ["unhelpful"], "9.3 6.2 7.8": ["shirtless"], "8.6 11.5 6.4": ["salesperson"], "1.8 7.1 6.5": ["patronizing"], "-6.6 3.4 3.1": ["remittance"], "2.6 9.0 -0.4": ["generalized"], "3.6 10.3 6.2": ["sensibly"], "-2.9 2.1 -3.6": ["examiners"], "14.1 7.1 6.4": ["ovens"], "4.3 14.4 -0.0": ["cooperatively"], "-2.5 24.1 14.2": ["herbicide"], "3.9 3.0 14.0": ["sitcoms"], "3.0 12.7 2.6": ["flagrant"], "13.2 2.1 11.3": ["sweeten"], "8.9 5.8 11.3": ["fluff"], "0.5 9.8 9.5": ["genders"], "-4.9 16.5 8.8": ["coverages"], "12.2 14.1 5.9": ["videogames"], "-0.5 16.1 5.8": ["delusions"], "13.3 17.4 8.8": ["benevolent"], "1.8 13.1 5.7": ["disorderly"], "1.3 5.4 7.3": ["heartburn"], "11.3 14.1 9.0": ["splintered"], "8.5 13.0 1.8": ["inconsequential"], "1.5 1.7 -8.1": ["congratulates"], "3.0 11.6 7.9": ["miscue"], "5.0 6.3 13.0": ["geologic"], "1.1 18.9 0.2": ["airstrip"], "0.0 6.1 7.5": ["embellished", "voiceband"], "-2.5 17.4 9.3": ["hopelessness"], "4.4 4.6 2.1": ["mismanaged"], "-2.7 8.1 3.2": ["longshot"], "-6.6 3.7 2.6": ["exhumed", "businesspersons"], "0.6 6.5 1.3": ["faxes"], "15.6 17.3 11.3": ["hoard"], "11.5 3.2 6.1": ["sketched"], "-1.6 7.4 3.5": ["canvass"], "-1.3 18.3 4.0": ["adherents"], "18.5 2.1 5.3": ["strapping"], "12.4 -1.1 16.9": ["stunted"], "2.2 2.0 6.8": ["bargained"], "6.9 26.1 5.5": ["radars"], "-2.3 11.0 0.6": ["hometowns"], "6.9 5.6 3.5": ["flawlessly"], "-10.5 13.9 8.1": ["scrimmages"], "3.6 8.7 6.3": ["forestall"], "25.3 7.0 1.1": ["salesmen"], "3.1 3.0 18.1": ["greenhouses"], "2.8 22.7 5.8": ["hardliners"], "1.3 2.8 3.2": ["adheres"], "-1.7 8.9 11.2": ["overspending"], "8.7 15.7 5.3": ["escalates"], "-1.7 13.3 21.0": ["buds"], "-3.2 6.7 -3.4": ["adjunct"], "-1.6 8.5 -0.7": ["disrepute"], "20.1 9.7 9.5": ["clunky"], "10.7 8.5 5.0": ["coexist"], "1.9 4.0 6.5": ["genomic"], "-7.1 20.0 4.2": ["sects"], "-1.4 11.9 7.0": ["actuarial"], "8.4 8.0 -3.7": ["simulators"], "0.7 2.2 -0.0": ["vignettes"], "7.0 5.0 3.4": ["entailed"], "8.0 19.4 3.4": ["splinter"], "-3.0 2.6 1.1": ["clarinet"], "-6.8 2.9 2.4": ["disappearances"], "4.2 7.2 10.2": ["renminbi"], "1.9 10.4 3.7": ["incrementally"], "1.6 0.3 -1.5": ["consults"], "-1.3 0.5 16.5": ["cultured"], "48.0 7.0 16.6": ["gargantuan"], "5.1 10.2 23.0": ["hives"], "3.9 0.2 3.5": ["streamlines"], "10.6 4.8 30.0": ["crunchy"], "11.8 3.1 -0.4": ["comfy"], "-0.1 8.0 9.5": ["dispositions"], "11.4 2.1 15.2": ["textured"], "4.0 1.4 6.6": ["lodges"], "-0.3 1.2 22.7": ["wafers"], "15.0 6.4 3.6": ["rotary"], "18.6 15.7 1.9": ["cubicle"], "21.4 7.0 5.3": ["brandishing"], "13.8 15.0 8.5": ["finder"], "0.2 5.3 1.9": ["dais"], "23.7 -1.6 4.8": ["mecca"], "4.8 4.1 14.5": ["lakefront"], "-0.0 5.7 5.1": ["convent", "potenti"], "4.0 4.0 5.1": ["chimed"], "13.1 15.7 11.2": ["cheerfully"], "-4.5 12.2 2.6": ["rusher"], "5.7 6.3 8.7": ["backhanded"], "5.9 13.8 5.8": ["blurry"], "10.2 19.2 8.1": ["intractable"], "4.5 10.6 1.6": ["zealous"], "0.7 4.8 -0.9": ["rifled"], "4.4 0.3 8.6": ["haggling"], "9.6 6.3 18.6": ["flourishes"], "5.4 2.6 8.9": ["cabling"], "11.3 2.1 6.9": ["milking"], "5.6 17.8 8.4": ["topography"], "5.7 15.2 8.9": ["slur"], "8.0 21.7 2.9": ["repelled"], "9.5 2.2 19.3": ["hemp"], "9.4 32.2 7.1": ["mercenary"], "3.1 0.6 11.5": ["chiropractor"], "-0.9 13.8 -6.9": ["disseminating"], "8.7 20.4 12.6": ["decoy"], "8.3 10.2 8.8": ["microcosm"], "12.1 4.3 9.2": ["sinkhole"], "3.8 7.6 56.8": ["flounder"], "-9.8 1.0 -0.1": ["clinician"], "5.2 9.2 6.7": ["grossly"], "12.1 12.7 7.8": ["symbolically"], "14.7 -0.5 7.9": ["sprouting"], "10.2 12.5 11.8": ["chuckling"], "3.5 12.9 7.8": ["halfcourt"], "13.0 19.7 5.7": ["stalker"], "17.2 15.7 8.1": ["ops"], "2.9 18.5 9.8": ["forested"], "9.6 4.5 7.6": ["jostling"], "1.4 -1.6 6.9": ["allocates"], "-0.7 -1.5 9.1": ["midyear"], "8.7 7.4 4.4": ["navigated"], "16.1 2.0 9.4": ["largesse"], "16.8 -4.4 7.6": ["swanky"], "-2.2 -0.2 -0.5": ["authoring"], "-2.4 17.4 4.8": ["empirical"], "10.7 11.2 17.1": ["pooch"], "5.2 8.9 4.7": ["ballparks"], "6.6 17.0 10.6": ["subtlety"], "16.8 7.6 19.0": ["gusher"], "6.0 6.9 -2.4": ["rebuked"], "2.6 10.9 6.4": ["descendant"], "3.8 9.4 6.8": ["mausoleum"], "0.2 -1.3 3.5": ["sixties"], "2.5 3.9 7.0": ["atypical"], "0.9 19.4 -6.8": ["massacred"], "10.7 7.4 4.0": ["friendlier"], "13.5 13.6 31.3": ["pigeon"], "0.8 15.1 13.6": ["indecision"], "8.7 12.2 7.9": ["giggle"], "5.5 2.9 0.3": ["harmonize"], "1.6 6.1 7.8": ["livid"], "17.8 4.2 -4.1": ["divested"], "8.8 12.1 8.3": ["nots"], "7.3 7.9 15.5": ["vernacular"], "-9.9 1.4 8.7": ["bereavement"], "0.5 12.8 0.9": ["conjecture"], "-2.7 -5.8 5.1": ["merited"], "7.6 13.2 7.4": ["spades"], "4.2 14.1 15.9": ["microbial"], "11.7 13.6 19.2": ["sustenance"], "-7.8 8.6 6.9": ["reformists"], "1.1 14.4 7.9": ["multiculturalism"], "5.0 4.4 2.1": ["optimizes"], "3.9 36.4 5.1": ["ambushes"], "0.4 6.6 6.5": ["parkland"], "4.9 10.7 7.5": ["edict"], "-0.3 5.7 5.9": ["boe"], "0.7 0.7 14.2": ["tuxedo"], "3.9 4.4 2.8": ["intranet"], "2.5 13.6 3.0": ["inkling"], "-0.0 4.1 -3.9": ["reinvested"], "4.1 4.8 6.2": ["stitching"], "-3.0 11.4 13.2": ["tombs"], "-1.1 -3.1 11.0": ["registrants"], "-1.5 5.0 4.9": ["apg"], "36.8 12.3 13.6": ["hulking"], "3.3 1.9 11.2": ["sassy"], "5.1 10.4 11.6": ["cravings"], "10.1 0.4 10.5": ["doling"], "8.7 10.3 12.4": ["enchanting"], "8.3 21.9 12.5": ["choppers"], "7.8 3.6 10.0": ["cobalt"], "3.8 28.4 -1.0": ["humiliate"], "3.8 14.6 8.6": ["infuriating"], "32.6 12.4 39.4": ["octopus"], "-5.2 9.1 12.3": ["realtor"], "21.2 6.5 13.4": ["smelly"], "17.3 18.5 10.8": ["unending"], "-12.0 15.3 2.3": ["biographer"], "3.7 10.8 -0.3": ["purged"], "9.5 20.3 8.8": ["machinations"], "14.3 3.1 -6.0": ["purporting"], "5.2 3.8 4.3": ["languish"], "0.4 5.4 -1.7": ["von"], "5.0 7.0 4.1": ["bonnet"], "8.1 21.7 8.4": ["existential"], "-0.3 8.8 7.4": ["vagina"], "-5.4 3.4 6.8": ["dermatologist"], "4.0 14.4 4.4": ["dilemmas"], "2.4 4.3 8.4": ["mains"], "11.0 9.2 20.9": ["glazed"], "2.7 -0.0 6.4": ["hormonal"], "-0.4 0.8 5.1": ["checkup"], "-1.7 6.8 1.6": ["transparently"], "20.5 8.3 4.0": ["nationalize"], "-3.5 10.6 -8.8": ["prejudicial"], "14.6 10.3 3.2": ["disintegrated"], "19.0 15.3 2.7": ["zooming"], "15.8 1.4 12.2": ["jacked"], "-1.2 5.1 5.9": ["brainstorming"], "1.4 3.1 2.6": ["entitles"], "3.7 -1.8 -1.8": ["finalization"], "-2.2 9.9 -0.7": ["ascertained"], "-4.1 7.7 2.6": ["camcorders"], "8.1 2.3 1.3": ["pasted"], "15.7 9.9 13.6": ["gaping"], "-1.0 8.4 3.9": ["considerate"], "-0.4 7.8 3.3": ["confessional"], "10.7 4.0 0.4": ["quizzes"], "14.5 10.5 6.2": ["shudder"], "0.1 9.5 -0.6": ["headsets"], "-9.4 2.5 6.2": ["soloists"], "-4.3 4.4 6.1": ["reinvestment"], "10.2 9.4 5.0": ["cryptic"], "-1.6 27.2 3.6": ["airman"], "2.0 5.9 1.6": ["selector"], "-7.0 1.6 -1.8": ["dermatology"], "1.1 13.8 6.3": ["flirt"], "11.7 8.8 5.8": ["downwards"], "1.8 5.3 2.1": ["corrects"], "0.8 10.2 2.2": ["adversely"], "6.5 4.1 1.6": ["biometrics"], "7.9 15.8 12.9": ["bullshit"], "5.1 10.0 4.2": ["constrain", "snippet"], "9.5 15.5 6.3": ["uncanny"], "6.2 8.4 5.7": ["seep"], "9.6 7.3 10.8": ["sweetest"], "17.4 7.3 8.3": ["straddling"], "10.3 2.1 11.1": ["mono"], "15.5 20.3 12.0": ["heartless"], "10.9 12.8 21.4": ["pines"], "-6.3 9.8 8.5": ["ballgames"], "12.3 -9.0 5.8": ["nixed"], "10.3 11.0 9.8": ["prickly"], "5.3 13.3 13.9": ["sly"], "6.2 -1.8 9.8": ["satin"], "8.2 12.5 3.8": ["binary"], "0.3 6.0 -0.5": ["excites"], "12.7 4.5 5.2": ["escalator"], "13.7 12.5 11.0": ["remnant"], "0.9 10.2 10.2": ["hamstrung"], "5.9 5.3 4.0": ["naira"], "1.8 8.1 -1.6": ["cautioning"], "-3.2 6.4 -6.0": ["imams"], "6.9 4.1 5.6": ["strictest"], "-4.1 8.5 12.7": ["opinionated"], "11.5 12.3 5.1": ["beau"], "2.7 12.0 46.2": ["fishes"], "11.1 0.4 -2.8": ["copycat"], "17.9 7.2 8.3": ["confectionery"], "5.8 20.9 7.5": ["sadistic"], "13.5 16.1 6.0": ["babe"], "4.9 8.7 10.3": ["sighed"], "1.9 7.5 1.8": ["twofold"], "4.3 11.5 27.0": ["saffron"], "17.3 13.7 9.6": ["roving"], "-1.2 13.1 10.9": ["climates"], "1.4 5.0 39.4": ["basil"], "15.4 17.5 5.7": ["fright"], "4.5 12.5 -0.8": ["silencing"], "6.4 7.5 1.2": ["ascension"], "0.2 0.5 6.8": ["reversible"], "23.3 16.0 18.4": ["ape"], "3.3 1.8 8.7": ["reigned"], "8.7 -1.0 6.9": ["inline"], "2.0 4.6 7.7": ["amphetamines"], "7.3 4.2 2.1": ["infrastructural"], "6.7 17.7 6.0": ["forefathers"], "2.0 6.6 5.9": ["tuner"], "16.1 5.6 5.5": ["prodigious"], "8.9 11.2 7.3": ["filth"], "-2.3 13.2 10.9": ["overcast"], "0.8 3.9 42.9": ["hatchery"], "12.2 -0.4 16.8": ["vending"], "15.7 -1.2 4.4": ["calculators"], "10.0 4.4 12.5": ["toasted"], "8.5 10.7 12.3": ["evergreen", "girfriend"], "16.0 2.0 1.3": ["harnesses"], "4.2 2.0 5.0": ["emeritus"], "13.8 9.9 7.9": ["consumerism"], "7.9 18.4 12.2": ["stings"], "6.9 1.0 1.0": ["precocious"], "10.7 11.7 7.3": ["slaps"], "7.4 10.0 6.2": ["blisters"], "9.5 6.1 12.7": ["gazebo"], "4.5 4.4 15.2": ["gags"], "-8.9 7.8 11.0": ["improv"], "5.1 21.5 0.3": ["abductors"], "11.9 12.7 9.9": ["piss"], "13.1 13.4 9.5": ["ineptitude"], "7.8 3.6 6.6": ["sweetener"], "2.2 8.6 8.8": ["beards"], "2.7 8.5 -6.9": ["airways"], "10.2 6.4 6.4": ["backroom"], "10.5 2.9 6.6": ["handyman"], "-2.8 11.2 -2.6": ["increment"], "22.7 15.9 6.6": ["hallowed"], "7.9 0.6 4.5": ["eruptions"], "6.8 12.9 4.5": ["hoods"], "12.6 14.9 10.3": ["inertia"], "4.0 -0.7 7.3": ["teenaged"], "13.2 4.9 30.8": ["cedar"], "7.4 6.4 1.2": ["picketing"], "5.8 12.8 17.0": ["decadent"], "12.8 20.3 3.4": ["figuratively"], "11.7 8.6 9.0": ["offshoring"], "0.5 1.9 0.2": ["lecturing"], "13.0 -3.6 5.5": ["sf"], "5.7 4.8 10.4": ["crass"], "10.8 11.5 9.7": ["millennia"], "16.7 2.9 10.4": ["suspiciously"], "0.3 5.8 13.2": ["craftsmen"], "3.9 16.5 10.6": ["compulsion"], "-0.5 5.2 8.2": ["harmonica"], "0.3 9.3 20.6": ["toppings"], "1.2 9.1 7.2": ["complicates"], "12.1 16.8 15.0": ["popup"], "1.4 11.4 -6.1": ["differentiating"], "2.1 11.7 5.1": ["numbness"], "8.2 0.9 6.0": ["fingerprinting"], "5.1 7.1 0.5": ["nursed"], "6.8 9.9 5.7": ["orbital"], "7.6 9.5 7.1": ["ode"], "6.2 17.7 1.0": ["logistic"], "-8.0 -0.3 1.5": ["concur"], "10.5 4.9 17.8": ["shacks"], "5.0 13.5 17.6": ["orbiter"], "4.9 16.9 7.3": ["temptations"], "14.0 13.6 9.9": ["smothering"], "6.0 16.4 5.4": ["rapists"], "9.7 2.0 2.2": ["costlier"], "0.9 11.3 4.2": ["plurality"], "5.5 28.6 2.5": ["revolutionaries"], "12.0 19.7 15.3": ["metaphors"], "-0.1 14.1 2.6": ["culpability"], "6.7 7.6 5.9": ["groping"], "5.1 15.1 7.2": ["prologue"], "3.9 -1.1 4.7": ["musings"], "9.5 2.8 5.9": ["lurch"], "4.8 7.2 19.6": ["wedges"], "8.9 7.7 -1.3": ["downplaying"], "16.7 8.9 10.8": ["fetish"], "-1.3 12.7 8.9": ["machining"], "-2.5 2.0 7.9": ["helmed"], "5.4 9.9 3.6": ["polices"], "4.5 -3.1 3.3": ["docs"], "0.4 8.7 3.8": ["misbehavior"], "21.8 24.1 7.5": ["horde"], "-6.2 8.2 -1.9": ["syllabus"], "18.9 -1.1 -5.9": ["revolutionizing"], "-0.2 11.3 7.2": ["anecdote"], "-3.5 5.3 -2.8": ["incidences"], "-0.1 6.4 -0.8": ["misappropriation"], "-4.2 6.0 0.8": ["incisive"], "5.9 6.9 33.9": ["berry"], "-6.8 6.3 6.3": ["guitarists"], "-3.9 5.6 -5.2": ["redacted"], "-1.3 -1.0 -0.1": ["stipulations"], "11.9 14.2 9.7": ["erupts"], "6.6 5.0 3.3": ["euphoric"], "1.0 2.6 0.7": ["rue"], "3.8 4.2 11.9": ["temps"], "7.4 20.4 28.7": ["baiting"], "-1.0 2.8 8.5": ["variances"], "15.1 18.1 11.4": ["adventurer"], "4.4 3.8 5.4": ["abated"], "-2.3 2.4 15.9": ["cargoes"], "8.1 8.6 -1.7": ["transformations"], "-2.9 5.0 0.0": ["anniversaries"], "3.2 13.1 6.3": ["exiles"], "-3.3 8.7 4.3": ["inhibition"], "13.7 7.6 10.2": ["freefall"], "3.1 13.0 12.0": ["goalscoring"], "3.7 -5.7 2.9": ["adjudication"], "14.7 2.9 4.1": ["malfunctioned"], "-0.2 2.9 6.2": ["stoves"], "6.0 20.2 6.4": ["perceives"], "14.2 7.8 8.9": ["spectacles"], "-4.4 23.5 10.0": ["selfishness"], "4.8 13.7 9.1": ["pranks"], "13.0 38.5 7.1": ["imperialist"], "0.0 9.2 2.1": ["innuendo"], "4.8 6.2 14.4": ["trifecta"], "11.3 2.0 1.3": ["seeped"], "13.0 5.9 3.4": ["gainer"], "6.2 5.1 18.2": ["foodstuffs"], "-4.8 2.3 14.6": ["foal"], "4.9 12.3 4.1": ["misjudged"], "8.3 12.3 10.5": ["messes"], "6.5 6.8 4.8": ["scampered"], "2.4 16.8 5.9": ["hymn"], "11.9 3.1 6.6": ["mugs"], "1.3 8.0 29.3": ["inlet"], "12.2 9.4 10.1": ["biceps"], "21.5 0.1 10.0": ["gaudy"], "5.7 13.1 7.1": ["exacting"], "10.7 17.8 15.4": ["wily"], "3.7 8.3 18.3": ["teaspoon"], "-4.6 5.5 2.6": ["handpicked"], "-5.6 14.4 7.5": ["impulsive"], "10.9 -3.7 5.7": ["brightened"], "2.4 7.5 7.5": ["stills"], "12.1 13.2 7.4": ["weep"], "4.6 9.2 38.3": ["estuary"], "-0.5 -2.0 7.2": ["wristbands"], "0.3 8.8 9.6": ["redistribute"], "11.5 6.2 14.6": ["heave"], "0.6 -4.5 3.4": ["raved"], "5.6 18.9 5.6": ["wearer"], "20.3 0.8 0.5": ["hawking"], "8.0 3.7 -0.8": ["adidas"], "-5.2 5.1 14.6": ["burials"], "1.6 19.4 5.7": ["subversion", "incurability"], "12.7 2.4 0.6": ["travails"], "9.5 5.8 7.4": ["recast"], "-4.0 4.4 20.6": ["bartenders"], "5.7 2.3 9.8": ["il"], "0.5 4.7 8.4": ["exacerbating"], "5.7 -1.3 2.9": ["technologists"], "10.4 7.1 20.5": ["delicately"], "5.8 7.1 4.9": ["schizophrenic"], "12.1 -2.7 6.9": ["crowning"], "7.5 8.0 10.4": ["exchequer"], "1.7 5.2 1.0": ["winded"], "16.0 2.2 8.5": ["underwhelming"], "4.3 10.8 6.9": ["rapprochement"], "10.6 8.6 9.7": ["classifieds"], "9.1 12.7 5.4": ["armchair"], "8.3 0.9 -0.6": ["dashboards"], "7.7 10.5 21.2": ["amber"], "28.0 10.6 36.3": ["penguin"], "3.6 9.8 14.1": ["iffy"], "5.4 2.3 2.3": ["invalidate"], "-0.6 16.3 1.1": ["criminally"], "3.3 9.7 1.6": ["jeers"], "8.1 -1.2 0.3": ["queued"], "15.8 3.6 5.7": ["stunner"], "7.8 -0.7 18.6": ["maids"], "7.5 5.6 4.6": ["acoustics"], "4.7 13.8 37.6": ["fowl"], "10.7 8.8 4.0": ["prospered"], "7.3 8.6 1.9": ["devalued"], "6.9 0.3 4.3": ["propriety", "reclaimable"], "7.9 15.3 2.8": ["amaze"], "6.9 3.6 4.5": ["laboring"], "-2.6 7.6 7.2": ["apprehensions"], "2.6 2.1 4.6": ["peptide"], "10.3 5.3 9.8": ["gals"], "-5.4 23.1 13.1": ["herbicides"], "7.9 8.6 6.7": ["irresponsibility"], "5.4 0.8 6.6": ["inspects"], "15.9 12.5 6.3": ["imitating"], "11.0 1.9 14.5": ["blender"], "19.8 20.5 8.2": ["trusty"], "7.1 22.1 6.8": ["eradicating"], "7.6 16.4 2.4": ["activates"], "11.3 9.9 31.1": ["buoys"], "-0.3 8.9 3.7": ["disenchanted"], "12.5 11.9 0.7": ["wherewithal"], "-4.4 1.5 9.5": ["decorum"], "14.3 21.6 7.8": ["inescapable"], "-0.8 2.4 -1.0": ["physicals"], "-6.1 20.4 3.8": ["evasive"], "-1.7 4.5 0.1": ["achievers"], "9.8 16.7 15.3": ["colonization"], "3.0 10.7 4.4": ["swerving"], "-3.3 -1.1 2.4": ["stylists"], "2.0 6.8 3.0": ["mailers"], "-3.1 -3.1 7.9": ["reapply"], "5.2 2.6 4.6": ["eke"], "5.2 10.2 9.1": ["loath"], "1.6 10.4 5.4": ["unelected"], "-0.1 0.6 12.9": ["iodine"], "1.6 5.2 -3.3": ["organist"], "0.3 5.5 11.3": ["wellhead"], "4.0 13.8 7.1": ["humbly"], "-2.0 0.6 1.9": ["carding"], "14.6 8.3 6.9": ["shreds"], "8.8 9.4 4.3": ["chasm"], "5.5 12.7 10.1": ["warmups"], "1.7 7.5 12.9": ["gully"], "8.0 13.3 7.7": ["toolbar"], "9.3 0.5 -1.0": ["chemists"], "-3.1 8.4 0.0": ["enlighten"], "3.2 6.4 11.4": ["virtualisation"], "11.7 5.5 5.4": ["elegantly"], "5.4 12.5 4.6": ["contaminate"], "6.5 11.3 7.7": ["handiwork"], "1.5 1.8 10.7": ["densities"], "6.2 8.8 0.9": ["deflecting"], "-1.2 7.1 20.5": ["masonry"], "7.3 1.5 10.0": ["precedes"], "3.2 12.6 2.4": ["saddest", "articulating"], "3.5 6.6 11.9": ["wrister"], "-7.1 10.7 -0.6": ["transferable"], "15.4 7.9 8.8": ["midafternoon"], "3.5 -4.8 1.7": ["formalize"], "-3.7 4.4 4.2": ["unfunded"], "12.2 3.8 4.1": ["courtside"], "0.5 9.7 2.9": ["marginalization"], "12.5 -1.2 -1.3": ["overcharged"], "2.6 1.6 4.8": ["participatory"], "9.2 19.2 5.6": ["resolutely"], "5.1 24.6 2.8": ["malignant"], "3.8 10.0 9.0": ["subtitles"], "4.3 10.4 4.3": ["turban"], "10.2 3.7 7.4": ["revs"], "8.0 0.7 21.3": ["trimmings"], "7.2 22.2 9.0": ["overpower"], "2.9 1.9 5.4": ["kilowatts"], "13.5 18.8 5.7": ["pariah"], "14.2 4.7 8.4": ["inching"], "4.2 1.4 11.2": ["tickled"], "-0.2 15.8 7.5": ["bunk"], "9.5 4.6 -0.3": ["wean"], "6.9 -1.9 2.2": ["encompassed"], "11.5 13.1 13.0": ["wrench"], "8.8 4.2 7.9": ["prosthetic"], "20.9 5.5 33.7": ["swan"], "10.0 4.8 16.8": ["sandstone"], "7.1 5.8 10.5": ["salvaging"], "-1.5 7.6 -4.9": ["scouted"], "4.6 6.7 8.8": ["discernible"], "2.3 0.8 -0.3": ["uptime"], "7.9 7.8 4.8": ["fuses"], "0.5 11.8 6.2": ["gist"], "10.9 5.9 11.0": ["dumpster"], "8.6 28.8 1.6": ["conspiracies"], "-2.1 13.4 3.3": ["refuel"], "-1.1 19.0 5.8": ["antiwar"], "-7.4 34.1 2.8": ["corporal"], "13.3 9.0 13.0": ["scrambles"], "29.5 15.5 11.8": ["wizards"], "4.4 -3.2 10.1": ["glam"], "0.1 8.5 -3.9": ["renounced"], "1.7 16.9 -5.8": ["jailbreak"], "5.7 4.9 5.8": ["lefthander"], "13.5 14.6 25.7": ["owls"], "4.6 4.0 -1.7": ["decibels"], "26.0 14.0 45.4": ["jellyfish"], "7.3 8.3 8.0": ["terraces"], "1.2 4.3 5.7": ["overrule"], "11.3 5.8 22.6": ["oatmeal"], "-2.8 7.8 -0.3": ["parried"], "1.0 -3.6 3.9": ["presides"], "-1.0 9.8 6.3": ["arbitrage"], "9.2 23.0 4.8": ["perish"], "14.2 -7.7 1.8": ["roadshow"], "-3.3 11.4 5.8": ["feuds"], "-3.4 12.8 9.8": ["powerplay"], "16.6 15.3 6.7": ["avatars"], "-7.2 11.0 0.1": ["reintegration"], "8.2 5.9 6.7": ["workspace"], "17.1 11.4 0.0": ["shamed"], "-0.8 5.6 2.7": ["thrillers", "vandalisms"], "20.8 17.1 11.6": ["stomp"], "-3.2 2.3 3.4": ["intravenous"], "8.7 2.7 -0.4": ["shunning"], "13.8 2.0 1.2": ["pendulum"], "-2.4 -3.5 -4.1": ["canvassed"], "11.8 11.8 8.2": ["shoveling"], "19.9 3.4 6.1": ["squashed"], "-4.8 0.5 6.4": ["unfilled"], "-8.3 16.5 -3.5": ["pseudonym"], "0.9 -0.7 5.7": ["pocketbooks"], "9.8 4.0 29.9": ["mayonnaise"], "-3.7 11.5 6.6": ["conversational"], "7.8 4.3 5.7": ["radiant"], "1.6 1.4 0.6": ["metros"], "2.5 7.4 1.8": ["divulged"], "12.9 10.6 4.5": ["lexicon"], "6.1 1.9 -3.3": ["exempting"], "2.6 1.3 16.9": ["horticultural"], "5.2 7.0 6.2": ["rubs"], "-2.1 7.8 9.3": ["disheartened"], "-4.7 10.5 4.3": ["tact"], "11.9 -2.6 7.8": ["strippers"], "-1.9 5.0 4.2": ["conforming"], "17.7 5.3 12.1": ["bouncy", "waterslide"], "-2.5 7.7 0.2": ["aliases"], "2.9 4.5 2.8": ["bests"], "6.1 6.3 23.7": ["hopper"], "3.0 9.6 6.1": ["dicey"], "4.8 9.6 3.5": ["bondage"], "0.3 5.9 5.8": ["cramps"], "8.9 -2.5 0.2": ["majored"], "11.1 9.3 15.3": ["slush"], "2.9 24.7 16.9": ["pathogen"], "6.2 9.4 7.8": ["thrice"], "11.4 8.7 8.5": ["sundry"], "1.0 5.0 7.1": ["displeased"], "1.6 12.7 3.1": ["inflame", "effectuates"], "0.8 6.1 8.1": ["pretentious"], "4.8 10.6 23.1": ["ornament"], "4.6 8.1 4.8": ["squander"], "-7.4 10.8 1.6": ["recuperate"], "10.4 10.9 2.5": ["epiphany"], "-4.3 8.7 -1.1": ["easements"], "7.9 12.5 8.2": ["mountainside"], "0.7 8.0 3.4": ["inhibits"], "2.0 13.8 14.9": ["midterm"], "7.2 1.3 6.6": ["provisionally"], "6.3 0.6 -2.9": ["poring"], "11.6 14.5 6.6": ["recklessness"], "-1.6 6.8 -0.0": ["attuned"], "12.2 7.8 14.3": ["buybacks"], "-7.8 7.0 2.3": ["implicate"], "-3.9 9.1 11.0": ["repo"], "8.9 4.2 19.4": ["fragrant"], "6.7 24.9 -2.1": ["plotters"], "11.4 12.8 8.2": ["prettiest"], "-0.8 3.4 3.5": ["bused"], "-3.8 5.9 6.1": ["resettled"], "11.2 19.4 3.7": ["worshiping"], "12.1 9.9 6.6": ["mistook"], "3.7 20.2 6.2": ["yardstick"], "11.9 15.8 10.3": ["mutated"], "-3.0 17.6 5.9": ["democrat"], "25.2 15.2 4.0": ["monolithic"], "9.8 6.3 31.7": ["delicacies"], "-3.0 3.4 7.8": ["psychosis"], "-1.1 -5.9 3.0": ["hostels"], "-1.8 7.9 9.1": ["constitutions"], "9.0 10.6 10.9": ["screwdriver"], "9.6 16.1 14.4": ["distaste"], "3.3 4.6 2.9": ["lubricants"], "-1.1 11.4 9.8": ["evaporation"], "10.1 -0.5 2.2": ["bludgeoned"], "1.9 4.4 6.3": ["chauffeur"], "5.7 1.5 6.8": ["courthouses"], "5.9 8.8 41.5": ["saltwater"], "15.0 34.5 11.6": ["merciless"], "2.2 7.0 8.0": ["hastened"], "-7.6 8.5 11.4": ["colonoscopy"], "14.6 -0.6 8.5": ["tote"], "7.1 2.4 2.8": ["unapproved"], "15.6 8.7 9.6": ["flatten"], "-6.3 1.6 12.5": ["spousal"], "23.1 13.2 8.2": ["wasteland"], "8.1 10.1 7.3": ["waltz"], "7.2 -3.6 8.1": ["tasteful"], "8.1 10.3 23.0": ["bead"], "1.8 8.9 6.8": ["flustered"], "4.9 14.7 9.6": ["overbearing"], "4.6 1.7 8.6": ["dub"], "3.9 5.6 4.4": ["benzene"], "-2.8 13.8 3.1": ["inferred"], "16.6 12.9 11.0": ["morph"], "13.3 13.8 3.7": ["urinating"], "-1.7 20.3 4.4": ["defectors"], "9.2 2.7 5.8": ["predominately"], "3.3 14.9 3.0": ["resists"], "-6.9 14.6 15.9": ["strays"], "3.5 5.8 2.4": ["dispensation"], "3.4 10.9 -0.8": ["orbits"], "11.9 21.6 5.5": ["ravages"], "-0.1 6.5 10.7": ["passable"], "-6.2 16.8 9.3": ["improvise"], "0.0 9.7 0.5": ["accomplishes"], "2.6 3.1 -0.4": ["mediating"], "4.2 10.5 13.4": ["climatic"], "4.7 8.7 1.4": ["immediacy"], "6.4 -4.9 41.4": ["caviar"], "-1.6 7.4 15.9": ["tenderness"], "7.1 -0.2 11.4": ["constructions"], "-5.6 5.5 2.9": ["foreclose"], "8.8 10.8 6.5": ["orchestrate"], "3.7 7.5 9.7": ["thinned"], "4.6 -1.0 10.6": ["housewives"], "-1.2 11.4 11.7": ["easygoing"], "-1.1 20.2 8.3": ["volleys"], "15.1 9.5 14.3": ["moons"], "8.9 11.2 10.0": ["rarest"], "5.4 15.1 8.6": ["anyways"], "5.4 0.3 2.3": ["pdf"], "-1.4 14.1 5.0": ["witchcraft"], "7.9 6.9 8.4": ["bask"], "1.7 3.6 3.7": ["paise"], "1.5 -2.3 6.4": ["se"], "1.9 1.3 11.2": ["bookmark"], "6.4 0.1 5.0": ["vibrancy"], "-4.6 15.0 1.4": ["empathize"], "12.1 0.6 2.8": ["caromed"], "10.1 10.9 5.7": ["stunningly"], "13.9 15.2 2.3": ["hooligans"], "5.7 10.1 22.5": ["ballast"], "15.7 12.1 15.5": ["pun"], "-8.8 13.2 9.1": ["electors"], "23.6 5.4 4.9": ["rocketing"], "6.5 9.7 21.1": ["pigment"], "10.2 10.4 4.2": ["constellation"], "-1.1 4.9 -1.0": ["occured"], "16.8 -0.9 -5.3": ["forerunner"], "2.4 15.5 -3.1": ["prophetic"], "1.9 11.5 2.6": ["justifiably"], "11.2 3.8 0.7": ["toiling"], "1.5 10.1 8.0": ["computation"], "11.5 13.8 24.3": ["crocodiles"], "4.7 5.4 16.3": ["floater"], "-4.8 11.5 4.7": ["victimization"], "18.2 15.5 1.6": ["apocalypse"], "5.5 6.3 12.4": ["overkill"], "4.7 9.2 13.2": ["sprinkler"], "0.6 18.9 3.7": ["subvert"], "-2.2 13.6 11.3": ["assimilation"], "-2.8 7.2 7.6": ["desegregation"], "-4.0 17.6 4.7": ["impassable"], "-0.5 1.1 10.9": ["rec"], "3.5 -0.0 -2.2": ["des"], "-2.7 9.1 3.3": ["scarring"], "11.0 18.1 1.3": ["holdouts"], "2.9 -0.1 14.4": ["rims"], "-5.7 18.9 9.9": ["realist"], "-1.0 15.7 5.9": ["alibi"], "8.5 -0.6 5.5": ["voluminous"], "-0.7 5.9 13.3": ["sevens"], "6.4 -0.5 -3.9": ["pipped"], "9.7 11.8 8.4": ["recreating"], "18.3 11.8 4.8": ["prowl"], "25.5 10.8 10.4": ["kingpin"], "-2.4 27.9 6.1": ["servicemembers"], "-5.2 11.3 0.1": ["facilitators"], "2.3 5.1 -3.4": ["entertains"], "1.6 4.8 4.1": ["tightest"], "-10.9 -2.0 9.4": ["reprints"], "10.3 -1.8 17.0": ["sizzle"], "-2.5 0.2 6.2": ["scrapbook"], "6.0 13.2 11.9": ["undercutting"], "-4.6 8.2 13.3": ["parenthood"], "7.3 12.6 8.2": ["ascending"], "8.2 10.7 6.5": ["unbridled", "counterpoised"], "7.4 18.0 0.2": ["pacify"], "7.1 21.2 30.8": ["foxes"], "11.1 17.8 4.0": ["fortify"], "66.6 13.6 9.5": ["titan"], "15.4 5.1 5.1": ["blister"], "2.1 7.7 7.1": ["despondent", "davunetide"], "8.6 8.5 5.7": ["bereft"], "1.3 10.5 5.4": ["geophysical"], "-3.9 12.4 23.6": ["ale"], "-2.1 11.8 6.6": ["disillusionment"], "16.1 4.9 13.2": ["skeletal"], "6.3 -3.1 6.8": ["pileup"], "-9.3 0.4 8.3": ["diocesan"], "17.8 16.0 14.9": ["parlance"], "17.3 9.1 6.9": ["tilts"], "18.4 -5.2 -0.6": ["branched"], "7.2 7.8 6.3": ["falters", "industriousness"], "4.8 9.6 1.5": ["spurious"], "10.0 3.2 16.4": ["planters"], "0.7 6.7 3.2": ["artiste"], "0.0 4.2 0.7": ["fairest"], "-2.1 0.9 4.9": ["soundtracks"], "23.1 3.0 18.1": ["translucent"], "27.2 19.1 35.7": ["lizard"], "-5.1 10.0 0.1": ["unpunished"], "-1.3 12.7 9.3": ["avalanches"], "0.7 8.3 0.9": ["jeered"], "15.0 1.6 7.6": ["tot"], "-5.7 6.7 16.1": ["winemakers"], "-0.8 4.0 5.5": ["reticent"], "-2.6 12.9 5.0": ["resented"], "6.0 15.2 17.4": ["canines"], "6.3 -1.5 20.5": ["spiced"], "22.2 14.0 5.4": ["geniuses"], "15.5 15.2 33.8": ["mammal"], "10.3 0.6 -0.1": ["eked"], "-3.4 1.7 -0.4": ["defibrillators"], "9.6 3.9 -0.4": ["equating"], "10.8 5.1 5.0": ["reveled"], "10.6 5.7 64.2": ["lobsters"], "3.2 3.9 1.2": ["raving"], "1.4 6.2 14.2": ["chromosomes"], "1.8 0.9 11.7": ["clustering"], "-0.1 26.4 9.6": ["landmines"], "5.1 8.3 4.1": ["quantified"], "7.5 11.7 2.7": ["gullible"], "1.5 -2.8 4.9": ["arranges"], "3.3 3.2 8.4": ["eyeglasses"], "10.5 2.3 9.4": ["snappy"], "5.6 -1.6 -0.1": ["bookkeeper"], "5.5 8.5 5.6": ["esoteric"], "3.0 9.3 9.7": ["tort"], "6.9 12.5 8.9": ["shortsighted"], "3.6 7.3 4.6": ["aerodynamics"], "6.2 -3.6 8.5": ["somethings"], "9.5 22.2 11.7": ["outrun"], "4.2 2.8 5.8": ["infusions"], "8.4 5.0 4.6": ["sedentary"], "-1.2 13.4 10.1": ["superstitious"], "15.5 12.1 16.2": ["jagged"], "2.4 2.5 11.0": ["artefacts"], "9.4 8.1 9.1": ["syndicates"], "12.0 15.4 8.6": ["encampment"], "7.2 5.2 6.4": ["householders"], "19.4 5.2 9.2": ["sideshow"], "3.1 -2.7 10.5": ["linens"], "-4.1 5.1 4.5": ["keyboardist"], "2.3 1.6 6.1": ["latch"], "-0.6 5.8 3.7": ["nineteen"], "6.6 4.3 1.4": ["unconvincing"], "4.1 8.3 -3.0": ["emotive"], "13.5 10.1 1.4": ["remade"], "2.5 5.2 9.7": ["raps"], "9.1 8.9 15.9": ["barbecues"], "16.0 0.9 3.2": ["likens"], "5.2 11.3 2.8": ["attentions"], "-3.6 2.7 0.7": ["overtimes"], "11.8 18.8 3.1": ["capitulation"], "0.5 3.6 5.5": ["midstream"], "-12.6 2.5 3.5": ["vocalists"], "9.6 18.0 10.1": ["sneeze", "sfx"], "4.3 4.1 17.2": ["tablespoons"], "9.1 7.0 11.5": ["haphazard"], "-2.7 8.2 1.8": ["outscore"], "9.9 13.1 10.7": ["plagues"], "17.3 19.6 15.0": ["inverted"], "7.1 9.5 8.6": ["bathe"], "-4.0 12.2 -2.0": ["astray"], "17.6 29.9 4.4": ["superpowers"], "0.3 -0.9 8.8": ["anorexia"], "3.1 12.9 6.6": ["incomparable"], "5.2 7.4 3.2": ["caustic"], "5.7 20.8 7.4": ["blitzing"], "19.5 21.6 5.4": ["ominously"], "-7.4 7.2 10.4": ["hardcover"], "11.5 10.7 8.0": ["malfeasance"], "19.2 5.6 8.8": ["flexing"], "-3.8 10.6 -0.5": ["invocation"], "15.1 14.7 22.3": ["arctic"], "6.9 10.5 5.1": ["exerting"], "1.2 10.5 3.3": ["ranting"], "15.3 5.2 8.2": ["gaggle"], "-1.8 5.0 9.5": ["rounders", "electrologist"], "9.1 18.5 4.2": ["skeptic"], "-1.5 6.5 10.2": ["subgroups"], "8.5 15.8 22.5": ["propeller"], "-8.2 30.0 4.5": ["tactically"], "17.7 10.8 -0.9": ["masquerading"], "2.8 -3.9 1.3": ["partied"], "13.0 1.3 4.5": ["trove"], "11.0 8.8 4.0": ["undeterred"], "6.1 8.3 9.5": ["radiator"], "8.7 6.7 1.9": ["diagrams"], "9.0 9.7 5.9": ["wields"], "20.2 2.2 -0.1": ["nondescript"], "18.1 11.9 9.0": ["diagram"], "9.1 3.4 -0.0": ["centralize"], "23.3 10.5 17.5": ["bobbing"], "11.2 13.0 10.9": ["asses"], "0.2 9.4 12.4": ["alloy"], "4.4 11.5 2.4": ["discloses"], "3.9 7.0 1.9": ["mathematically"], "8.8 16.5 8.6": ["omen"], "5.6 -3.4 5.7": ["strollers"], "7.3 8.3 4.8": ["chemically"], "-1.4 9.1 5.2": ["weeding"], "5.8 13.1 11.5": ["misstep"], "2.4 -3.3 -3.0": ["relinquishing"], "1.9 4.7 0.2": ["wavered"], "7.0 -4.0 4.5": ["triplets"], "8.1 3.3 1.2": ["knifepoint"], "15.4 4.9 6.5": ["luminous"], "6.6 15.6 7.7": ["cliches"], "8.4 24.6 3.1": ["paramilitaries"], "7.6 1.3 5.9": ["shillings"], "8.3 7.5 5.8": ["compartments"], "-3.8 8.1 0.8": ["posthumous", "poignancy"], "-1.2 10.1 2.4": ["neurosurgeon"], "-0.6 3.2 5.1": ["mementos"], "4.6 0.7 5.3": ["insures"], "12.8 7.1 -0.7": ["malfunctions"], "-4.6 5.5 11.4": ["hairstyle"], "1.5 -0.9 4.5": ["seventies"], "8.3 16.4 7.0": ["maddening"], "10.5 6.1 18.4": ["sprout"], "10.0 2.6 6.1": ["lightest"], "1.0 0.9 3.9": ["stipulate"], "7.4 18.0 22.7": ["fungi"], "-1.4 6.7 0.6": ["seclusion"], "8.0 15.0 9.1": ["cameramen"], "2.2 10.4 7.1": ["swerve"], "16.0 1.6 16.7": ["silky"], "3.5 5.3 13.0": ["operatic"], "-2.6 7.9 18.5": ["acidity"], "11.4 3.2 -0.6": ["parading"], "10.8 14.0 20.6": ["marbles"], "9.1 8.6 27.3": ["sliders"], "2.6 -4.5 1.7": ["blogged"], "3.4 13.2 7.3": ["arithmetic"], "4.5 2.8 17.2": ["ho"], "5.6 6.9 8.3": ["buffers"], "-4.5 11.7 -1.1": ["practicable"], "6.2 9.8 11.5": ["cronyism"], "17.1 12.4 23.4": ["skinned"], "5.6 7.8 4.7": ["repatriate"], "6.4 8.0 32.2": ["jetty"], "-5.1 0.9 3.2": ["postmarked"], "1.8 7.2 -1.6": ["simplification"], "5.2 10.1 -1.6": ["guarantor"], "6.1 12.3 7.5": ["deepens"], "10.9 -4.8 -1.6": ["dabbled"], "-0.3 9.0 16.0": ["horsemen"], "4.5 0.9 13.6": ["carpentry"], "-1.5 5.5 6.8": ["sedatives"], "1.3 16.9 5.8": ["anarchists"], "16.7 7.6 11.6": ["clawing"], "6.5 -0.7 3.4": ["belies"], "-0.1 12.9 9.3": ["intents"], "-2.4 0.4 9.6": ["quilting"], "9.4 -6.3 -0.6": ["overflowed"], "5.1 7.7 10.7": ["shoo"], "19.4 7.2 14.1": ["gobbled"], "-0.2 14.3 -1.3": ["constructively"], "6.0 9.3 23.1": ["rearing"], "6.1 1.8 1.1": ["renown"], "13.7 13.1 23.9": ["eaters"], "11.7 -1.6 5.5": ["sputtered"], "20.9 15.8 16.5": ["bulldog"], "0.5 -3.5 8.2": ["evictions"], "5.8 12.8 6.1": ["instigating"], "17.9 8.1 31.7": ["pancake"], "6.0 -2.0 1.3": ["thronged"], "1.1 0.7 4.5": ["markup"], "8.8 10.5 -3.6": ["vociferous"], "16.7 17.4 11.7": ["gambit"], "4.2 1.1 4.3": ["anthropologist"], "2.6 4.4 3.6": ["epitomizes"], "13.3 11.6 5.2": ["ceding"], "5.7 15.1 2.7": ["biochemical"], "10.9 8.9 6.3": ["friendliness"], "-3.2 10.1 6.4": ["lacerations"], "4.4 3.0 12.2": ["lengthening"], "16.8 0.9 -8.9": ["rebranded"], "3.1 5.6 6.0": ["upholstery"], "6.3 0.0 -7.7": ["authenticate"], "20.8 13.3 10.2": ["devoured"], "1.2 0.1 8.3": ["lengthened"], "2.4 0.3 11.2": ["painkiller"], "2.7 24.1 10.1": ["smallpox"], "-8.1 10.2 5.2": ["hereditary"], "4.7 -1.1 3.8": ["quieted"], "12.3 10.3 5.0": ["affectionately"], "-4.4 10.5 3.5": ["infielders"], "-5.0 4.2 2.5": ["decentralization"], "2.0 12.9 1.0": ["nominally"], "0.3 17.8 9.8": ["erodes"], "5.3 4.5 11.2": ["corralled"], "5.2 7.1 10.1": ["setups"], "-17.9 3.6 4.1": ["playwrights"], "0.3 3.9 7.4": ["inhibited"], "7.9 14.7 14.0": ["afterlife"], "7.9 8.3 25.9": ["shipyards"], "4.3 9.2 5.5": ["ulcers"], "5.0 5.6 6.3": ["greening"], "0.0 6.7 5.7": ["reversals"], "9.0 5.8 11.4": ["hibernation"], "16.6 17.9 5.3": ["simulating"], "-5.8 5.6 18.7": ["watersheds"], "8.3 -1.6 4.4": ["ruckus"], "20.4 8.9 2.8": ["plucky"], "16.7 13.2 31.3": ["raccoon"], "5.2 6.9 3.3": ["detectable"], "13.7 13.7 11.1": ["watcher"], "1.0 -0.4 -2.5": ["authenticated"], "-3.8 10.8 5.7": ["misfired"], "0.5 14.3 3.8": ["contrarian"], "12.7 16.8 9.7": ["horrid"], "4.6 9.5 4.4": ["reassert"], "-3.3 5.5 27.5": ["subsistence"], "4.7 -5.6 7.3": ["jumpstart"], "14.6 18.5 4.3": ["minefield"], "0.7 2.0 0.2": ["encoded"], "1.4 11.0 -2.0": ["focal"], "-0.5 22.6 7.6": ["dissenters"], "2.7 3.8 -2.0": ["elevates"], "9.2 12.6 3.2": ["awed", "quietus"], "8.0 4.8 11.9": ["expats"], "8.5 9.4 6.1": ["vexing"], "6.2 5.5 6.3": ["byproducts"], "3.1 5.6 -2.3": ["contractions"], "8.3 11.5 3.8": ["deranged"], "-6.3 9.0 8.9": ["livable"], "9.5 7.9 6.3": ["uninspired"], "5.1 4.8 14.7": ["clubbing"], "3.0 9.8 5.0": ["realign"], "6.4 11.2 6.3": ["handshakes"], "6.1 9.5 5.3": ["tearfully"], "14.5 -0.4 16.1": ["subsea"], "13.6 14.1 21.2": ["leopard"], "2.2 10.5 0.3": ["characterizing"], "3.6 3.0 5.8": ["retrenchment"], "-1.5 11.0 6.1": ["bushfire"], "8.5 -2.4 0.5": ["robustness"], "5.1 9.4 7.8": ["thoughtfully"], "-0.3 9.3 9.8": ["oxide"], "9.1 22.6 12.8": ["thee"], "13.9 15.9 17.5": ["climactic"], "-0.8 10.1 2.4": ["oblique"], "3.2 14.2 7.8": ["surrenders"], "14.1 5.0 8.6": ["peered"], "-1.5 4.9 5.3": ["quadriceps", "crematories"], "17.0 6.0 8.3": ["orgy"], "8.5 9.5 4.8": ["spew"], "-4.3 7.1 1.7": ["recanted"], "11.2 10.8 25.1": ["spoons"], "5.3 2.1 13.8": ["fleece"], "3.8 0.3 3.6": ["eighties"], "9.2 4.1 2.7": ["intestinal"], "9.4 12.9 4.9": ["indisputable"], "3.4 9.4 0.4": ["routs"], "14.0 -0.8 4.7": ["decry"], "7.9 7.2 5.2": ["accretion"], "0.3 12.2 6.5": ["unapologetic"], "3.0 26.3 7.2": ["sniping"], "8.4 28.7 7.9": ["poisons"], "1.4 35.0 1.8": ["hideouts"], "9.2 12.2 6.6": ["intrepid"], "-4.5 15.3 5.5": ["clique"], "0.7 12.9 10.8": ["ambivalence"], "6.2 4.0 7.4": ["notables"], "2.8 9.7 6.7": ["tiresome"], "6.3 24.1 10.1": ["pretends"], "5.0 10.3 3.8": ["calibrated"], "-1.5 4.7 8.5": ["condensate"], "8.4 -1.0 7.4": ["genomics"], "5.8 16.7 7.4": ["stimuli"], "-2.2 22.2 1.8": ["indefensible"], "12.7 5.4 28.9": ["macaroni"], "13.1 7.2 1.8": ["lurid"], "17.2 5.5 3.8": ["uninspiring"], "-5.0 11.7 -5.0": ["unrecognized"], "-8.2 3.3 11.3": ["circumcision"], "8.0 7.4 16.9": ["hoof"], "0.2 9.6 0.7": ["sweeper"], "3.2 10.9 3.9": ["adapts"], "12.0 9.4 5.2": ["effigy"], "-1.1 1.0 -2.9": ["exudes"], "0.1 4.6 17.3": ["collagen"], "6.8 28.3 7.3": ["serviceman"], "-0.5 16.5 5.8": ["surrogates"], "3.8 17.8 10.7": ["dogma"], "-2.8 24.5 7.8": ["eventuality"], "2.3 6.1 6.8": ["stimulant"], "4.1 3.1 17.8": ["nutty"], "11.6 0.8 8.0": ["helium"], "16.2 19.4 11.1": ["unfathomable"], "8.2 -4.8 0.5": ["multilingual"], "5.2 3.5 6.7": ["theatrics"], "17.1 -3.6 2.3": ["shelve"], "11.8 17.7 12.0": ["gesturing"], "1.4 12.6 7.3": ["inflexible"], "-0.3 26.8 7.2": ["countermeasures"], "3.2 -1.3 0.0": ["slugged"], "-2.8 15.2 2.9": ["profess"], "20.2 23.7 2.2": ["encircled"], "6.9 10.6 9.6": ["decommissioned"], "7.2 19.2 18.4": ["doves"], "0.8 -4.9 4.5": ["registries"], "10.5 5.2 6.9": ["fiddling"], "9.8 6.6 12.4": ["silliness"], "7.1 9.7 9.5": ["commonsense"], "5.9 0.7 2.5": ["cachet"], "23.3 7.8 6.0": ["costliest"], "12.7 3.5 0.3": ["toying"], "8.5 12.7 -0.0": ["embedding"], "22.0 17.4 14.2": ["ghostly"], "0.9 8.0 18.6": ["artisan"], "-0.7 3.4 -0.9": ["distilled"], "3.3 7.5 10.7": ["intestine"], "-3.9 1.6 4.6": ["accrual"], "-7.2 0.5 2.0": ["unaffiliated"], "5.9 2.0 10.0": ["dyes"], "-1.0 7.2 6.3": ["meted"], "4.0 6.1 21.8": ["sediments"], "2.2 22.3 8.7": ["navigator"], "2.0 18.8 4.6": ["incurable"], "-1.8 14.7 3.6": ["eloquently"], "9.9 10.8 11.2": ["ethereal"], "4.6 8.0 5.0": ["blockades"], "-1.5 4.8 13.1": ["watercolors"], "-9.4 15.2 2.9": ["reelected"], "5.0 28.1 8.0": ["motherland"], "-4.5 3.2 1.2": ["creditable"], "9.6 12.2 9.1": ["mechanically"], "1.4 10.3 -0.2": ["energizing"], "-6.9 0.0 7.5": ["fifties"], "8.4 9.1 -4.9": ["unassailable"], "12.5 9.7 8.9": ["abandons"], "-4.5 1.7 10.5": ["virginity"], "16.4 -2.8 4.3": ["axing"], "16.4 3.0 5.4": ["rollercoaster"], "10.1 -3.8 11.0": ["pricier"], "6.3 11.5 1.1": ["asterisk"], "9.1 9.2 42.4": ["corals"], "7.1 9.8 8.2": ["contemplates"], "0.8 9.8 16.7": ["senatorial"], "0.1 6.6 4.3": ["parred"], "16.5 10.1 7.5": ["geo"], "4.9 9.8 1.6": ["intensively"], "5.9 4.9 -0.8": ["fazed"], "7.1 2.8 -1.5": ["wearable"], "-0.4 17.3 1.6": ["wronged"], "2.6 6.7 6.4": ["anomalous"], "9.1 6.0 8.4": ["opulent"], "0.3 25.1 11.9": ["armistice"], "4.5 7.0 1.5": ["facebook"], "-0.8 10.8 6.9": ["policymaking"], "-1.4 16.3 3.2": ["assimilate"], "9.1 -1.8 -0.1": ["unremarkable"], "-1.7 10.8 12.1": ["interstates"], "11.5 16.4 26.3": ["coastlines"], "1.0 3.3 1.5": ["inherits"], "2.2 18.6 -1.6": ["abhorrent"], "12.7 -1.4 10.9": ["polyester"], "9.5 14.1 5.4": ["passerby"], "3.6 8.1 10.4": ["tellers"], "-1.2 6.1 8.7": ["consecutively"], "-3.9 11.0 -1.1": ["airway"], "2.0 5.8 9.6": ["counterpoint"], "5.2 5.0 1.2": ["nomadic"], "-6.9 7.9 11.9": ["backhaul"], "2.8 8.7 7.1": ["franc"], "8.6 3.6 3.5": ["detergent"], "0.0 3.7 10.4": ["raring", "fromager"], "4.8 7.2 3.9": ["contextual"], "14.6 28.0 3.5": ["vanquished"], "-7.1 3.8 3.4": ["obstetrics"], "1.0 11.9 6.8": ["politicking"], "-5.9 8.1 4.6": ["understudy"], "5.9 10.2 12.6": ["hillsides"], "-7.3 3.7 3.6": ["menswear"], "5.1 6.4 23.5": ["canoes"], "-1.2 14.8 10.2": ["uninhabitable"], "24.3 7.6 26.5": ["cubes"], "-4.4 0.5 -3.3": ["precluded"], "-0.3 10.9 2.2": ["unquestioned"], "-4.7 1.0 -3.7": ["capt"], "-5.2 1.4 4.7": ["compensatory"], "6.0 9.0 7.7": ["surveyor"], "4.4 24.6 10.9": ["sinful"], "11.9 18.4 10.6": ["outstretched"], "0.8 3.4 9.1": ["benching"], "-1.0 12.6 6.5": ["ifs", "medicalphysicsweb"], "15.0 7.6 7.4": ["macabre"], "9.0 6.5 13.7": ["candlelight"], "-0.1 7.8 4.1": ["mesothelioma"], "6.1 17.1 7.5": ["muzzle"], "3.1 3.1 -2.3": ["satisfactorily"], "-4.9 7.6 11.2": ["oncologist"], "0.9 13.2 -2.4": ["expelling"], "4.7 7.3 9.2": ["underachieving"], "8.8 5.5 13.1": ["partygoers"], "10.6 9.9 14.3": ["lingo"], "-3.0 4.5 10.1": ["fatherhood"], "1.4 4.0 3.2": ["slotting"], "5.6 27.0 4.9": ["dogfight"], "6.1 10.7 7.0": ["centerfield"], "8.2 15.1 12.5": ["shards"], "-8.4 9.7 26.3": ["paddy"], "-6.0 7.4 -0.2": ["convicting"], "25.8 6.7 12.0": ["tumbles"], "21.1 8.7 15.7": ["windmill"], "0.6 13.0 5.9": ["apathetic"], "-4.2 5.4 6.6": ["alcoholics"], "18.2 7.5 15.1": ["gorillas"], "9.4 3.2 12.5": ["crooner"], "6.6 6.2 9.1": ["dissect"], "3.6 14.6 11.1": ["overreaction"], "5.8 4.8 4.5": ["decrees"], "-3.4 24.4 0.6": ["sedition"], "-10.4 8.6 11.5": ["demolitions"], "24.4 11.0 8.4": ["labyrinth"], "1.5 20.2 8.4": ["skillfully"], "-2.2 6.2 -0.4": ["manhandled"], "5.3 7.8 12.1": ["upshot"], "-2.1 11.3 7.2": ["inequities"], "7.7 -10.5 4.6": ["del"], "2.1 10.4 -1.5": ["ion"], "8.0 10.8 34.0": ["pike"], "0.3 6.8 -0.2": ["bettering"], "4.7 6.3 1.1": ["solidifying"], "13.9 7.3 2.8": ["retooled"], "11.6 10.0 -0.6": ["torching"], "11.4 11.4 11.5": ["trembling"], "1.7 24.9 3.8": ["hypocrite"], "17.1 10.6 28.5": ["cock"], "0.9 25.9 3.9": ["fundamentalists"], "8.7 12.9 5.5": ["holiest"], "3.8 -7.3 6.3": ["booklets"], "23.6 0.3 12.3": ["sagged"], "2.9 7.3 -3.0": ["bulldozed"], "4.9 19.1 8.0": ["forte"], "0.7 1.2 4.4": ["injectable"], "-0.7 6.3 7.4": ["congregants"], "0.9 2.6 15.1": ["strata"], "6.2 8.0 5.6": ["volt"], "3.7 4.2 3.0": ["overburdened"], "3.0 5.3 2.5": ["stuffy"], "6.7 11.3 -4.1": ["flammable"], "7.7 7.2 7.4": ["rearranged"], "-0.0 6.1 4.5": ["papacy"], "6.4 6.8 7.7": ["vicar"], "-4.2 -2.4 3.7": ["backlogs"], "-2.4 9.2 1.4": ["deplored"], "-0.6 3.5 19.2": ["bourbon"], "3.9 2.3 12.8": ["curls"], "10.4 8.7 8.4": ["discounters"], "1.7 13.7 13.0": ["depleting"], "-14.8 7.1 -3.0": ["morbidity"], "11.8 13.1 0.5": ["unrecognizable"], "8.2 1.3 6.0": ["virtuoso"], "5.4 3.5 10.7": ["creams"], "-4.6 2.7 2.4": ["schoolwork"], "16.0 -6.4 4.7": ["staid"], "14.3 5.1 13.1": ["fingered"], "27.5 4.9 8.0": ["cos"], "11.5 -0.2 10.4": ["lo"], "25.2 16.7 30.0": ["lizards"], "5.2 2.6 -0.0": ["hushed"], "0.4 9.6 4.2": ["exhorted"], "1.6 3.4 6.2": ["vivo"], "19.7 19.6 17.2": ["deity"], "16.9 1.7 -1.4": ["sniffed"], "24.8 13.7 11.1": ["wondrous"], "-4.0 10.1 2.4": ["libero"], "10.0 4.5 -0.3": ["ergonomic"], "5.7 3.5 2.0": ["sombre"], "14.8 1.4 10.4": ["yank"], "14.0 30.4 4.0": ["annihilation"], "11.8 8.0 9.4": ["wannabes"], "-0.1 19.0 2.7": ["memorize"], "9.7 7.8 8.8": ["placard"], "3.9 12.6 4.0": ["guesswork"], "10.7 5.5 6.7": ["jettisoned"], "0.5 10.6 2.4": ["incoherent"], "12.8 12.1 14.3": ["chimpanzees"], "-2.2 19.5 6.4": ["coercive"], "6.6 7.8 5.2": ["initiates"], "4.0 21.4 2.4": ["vendetta"], "-0.1 2.4 14.6": ["contraceptive"], "9.9 14.7 6.4": ["ascend"], "20.4 28.7 4.6": ["raiders"], "6.9 0.2 -5.9": ["aegis"], "2.5 13.7 5.1": ["skilful"], "0.9 9.8 4.4": ["divergent"], "5.2 -2.8 6.4": ["showmanship"], "5.3 14.6 5.2": ["immeasurable"], "3.8 14.6 7.7": ["prism"], "-5.8 9.3 9.1": ["incision"], "-2.6 4.1 10.1": ["technicals"], "0.6 4.9 -2.2": ["coincidental"], "16.8 18.1 18.9": ["manmade"], "8.4 11.4 7.3": ["corny"], "10.7 0.2 3.1": ["tumult"], "11.9 2.3 15.1": ["regal"], "0.2 4.6 6.2": ["socio"], "4.4 14.9 7.0": ["propagate"], "4.2 6.1 8.5": ["homerun"], "9.4 -2.9 5.2": ["fretted"], "13.4 0.6 30.9": ["walnut"], "12.2 38.6 11.7": ["minions"], "4.9 1.9 7.5": ["spar"], "4.0 10.1 3.5": ["cornerstones"], "-0.5 6.5 0.4": ["purified"], "17.8 8.3 6.3": ["dazzle"], "10.2 23.0 10.1": ["asteroids"], "9.7 2.3 0.9": ["doctored"], "4.2 7.1 9.5": ["barter"], "5.8 4.9 5.7": ["whittle"], "4.5 -0.4 3.2": ["normality"], "0.9 6.0 4.9": ["episodic"], "24.1 17.2 14.2": ["elves"], "18.4 -2.3 11.9": ["plunked"], "7.0 13.2 6.2": ["plundered"], "3.4 12.7 20.9": ["lice"], "-2.0 12.5 1.3": ["fatwa"], "3.6 7.9 13.1": ["parishioner"], "2.7 4.8 15.6": ["kindergartners"], "-4.8 0.8 10.7": ["excavations"], "3.5 11.1 7.9": ["windscreen"], "-0.4 14.8 4.3": ["burqa"], "3.8 8.6 25.8": ["shipwreck"], "-0.5 -0.1 -5.0": ["shuttled"], "11.8 1.0 3.4": ["upstaged"], "3.0 7.6 19.3": ["wildflowers"], "0.3 16.9 6.9": ["loner"], "10.4 11.0 11.2": ["gliding"], "4.9 16.1 4.3": ["uproot"], "4.2 6.3 2.9": ["coasting"], "16.5 14.7 8.6": ["mightily"], "-7.4 9.9 22.1": ["perennials"], "7.1 5.9 11.0": ["perennially"], "3.5 -7.5 -0.2": ["gestation"], "13.6 13.6 8.8": ["descends"], "11.4 3.6 3.1": ["conjures"], "10.4 0.5 15.8": ["cafeterias"], "-6.1 0.7 -6.4": ["unwell"], "7.6 0.9 10.9": ["railings"], "12.5 6.2 4.3": ["reinvigorated"], "1.9 -2.9 -1.3": ["dispelled"], "6.8 8.8 19.2": ["pellet"], "2.9 13.1 3.3": ["expend"], "5.3 15.0 10.3": ["momentary"], "0.4 1.7 -0.2": ["beatification"], "4.1 1.5 12.6": ["cramp"], "19.0 -3.2 15.1": ["kroner"], "5.3 4.5 -0.8": ["negotiates"], "-0.8 7.0 4.8": ["crossovers"], "6.1 11.0 9.4": ["digestion"], "-1.6 17.9 3.8": ["regressive"], "12.9 4.2 -0.0": ["cots"], "16.4 2.4 6.5": ["halving"], "16.9 8.3 4.8": ["fittingly"], "4.7 4.4 9.3": ["jobseekers"], "19.5 8.7 11.5": ["miniscule"], "7.2 10.6 1.8": ["rotates"], "4.6 7.9 -0.1": ["salient"], "29.7 27.6 26.8": ["dragons"], "-0.0 1.4 26.8": ["restaurateurs"], "5.0 0.2 -1.9": ["certifies"], "8.1 2.3 0.1": ["weaved"], "14.9 9.3 20.2": ["bog"], "2.7 11.2 0.7": ["subordinated"], "7.0 4.3 7.6": ["assembles"], "-0.6 13.3 6.1": ["stoop"], "10.4 0.7 1.6": ["spraining"], "-0.5 3.4 11.3": ["meds"], "-0.0 0.7 1.4": ["bridged"], "-8.1 -4.5 8.0": ["rehired"], "3.9 5.6 5.2": ["emphysema"], "-3.8 -2.5 3.4": ["convener"], "-3.0 15.3 0.8": ["liquidating"], "7.5 24.3 23.3": ["hatches"], "10.6 3.4 2.1": ["briskly"], "1.3 4.5 7.1": ["alternated"], "-4.3 3.9 6.1": ["swimwear"], "-1.7 3.8 13.8": ["hon", "particulier"], "1.9 7.5 6.9": ["grandstanding"], "7.3 6.1 10.2": ["loader"], "11.0 29.5 14.8": ["bastard"], "1.8 3.9 3.9": ["retrofitting"], "18.0 14.0 5.7": ["dislodged"], "10.4 8.6 38.3": ["fins"], "-6.5 15.0 -7.5": ["posthumously"], "10.7 10.2 7.2": ["cavities"], "5.0 13.2 22.3": ["seaport"], "8.8 4.6 12.2": ["balmy"], "15.2 9.7 -3.3": ["industrialist"], "4.8 8.4 9.2": ["incredulous"], "-4.4 -5.4 3.0": ["prenatal"], "7.4 14.1 8.2": ["scorned"], "1.3 7.7 -2.0": ["rebut"], "-5.0 1.7 6.4": ["saxophonist"], "12.2 5.2 0.7": ["stratosphere"], "6.0 6.7 -5.5": ["bestselling"], "7.5 22.8 0.1": ["infiltrating"], "8.2 -1.1 12.5": ["freewheeling"], "16.2 16.4 -1.8": ["remaking"], "-1.0 21.2 6.3": ["accusers"], "2.8 8.0 16.8": ["tablespoon"], "6.7 4.6 5.5": ["multichannel"], "22.2 -0.0 10.8": ["heft"], "-0.7 9.8 2.1": ["excelling"], "6.4 7.8 38.0": ["wharf"], "0.1 7.9 8.7": ["mower"], "18.2 4.5 2.9": ["unfurled"], "-4.9 12.4 2.5": ["paranormal"], "6.0 17.3 -2.0": ["steadfastly"], "1.8 10.0 7.7": ["yearn"], "2.3 7.5 -0.4": ["pleasurable"], "6.3 7.2 -2.9": ["berated"], "8.8 13.3 1.0": ["sabotaged"], "7.8 16.3 12.7": ["telemarketers"], "-1.2 3.9 -1.4": ["unblemished"], "7.3 -0.5 -1.9": ["peruse"], "10.6 4.9 26.7": ["flakes"], "21.9 11.4 12.1": ["pyramids"], "0.2 12.9 7.7": ["diehard"], "-1.5 24.6 12.7": ["warhead"], "0.4 3.1 -1.8": ["broadens"], "2.5 8.7 5.7": ["newsstand"], "13.1 9.8 15.5": ["chimp"], "17.5 2.1 8.5": ["pavilions"], "8.8 7.1 8.1": ["buckling"], "0.9 8.4 5.8": ["retool"], "-4.6 2.0 2.9": ["cameos"], "3.0 -0.3 14.8": ["ponytail"], "4.5 9.0 9.6": ["pavements"], "17.3 15.7 7.5": ["smashes"], "5.3 8.8 23.2": ["glaze"], "8.7 5.9 2.9": ["emulating"], "2.2 6.8 6.7": ["misplayed"], "5.5 12.6 2.7": ["astonishingly"], "6.9 2.9 0.1": ["backtracked"], "11.8 2.3 4.3": ["outstripped"], "15.0 6.6 10.9": ["nudging"], "-0.4 -0.7 -2.5": ["broached"], "12.2 9.8 10.1": ["droplets"], "8.8 16.5 -1.3": ["benefactors"], "8.4 13.1 7.0": ["gory"], "11.7 5.2 12.7": ["hippies"], "6.9 28.0 5.5": ["ruthlessly"], "12.2 13.9 10.6": ["masking"], "7.3 6.8 3.0": ["deregulated"], "-2.3 7.9 6.4": ["homily"], "17.2 4.6 0.0": ["greenest"], "-7.1 12.5 7.9": ["basemen"], "7.6 7.0 4.1": ["zeros"], "6.1 6.7 11.7": ["flouting"], "7.0 13.3 5.8": ["furthermore"], "-4.7 -4.0 6.1": ["detox", "asof"], "17.3 8.7 32.9": ["pickle"], "10.5 4.8 36.7": ["meatballs"], "-4.0 44.2 7.3": ["gunner"], "-7.4 11.8 1.5": ["understaffed"], "5.7 2.2 7.7": ["prepped"], "-2.4 4.2 0.5": ["necessitate"], "-1.3 7.1 6.6": ["campsites"], "2.5 0.8 4.9": ["alleviated"], "14.1 8.3 25.8": ["cupcake"], "6.2 9.5 4.7": ["voiceover"], "-0.1 13.0 4.3": ["abstraction"], "8.0 39.0 6.0": ["paratroopers"], "0.4 8.6 4.3": ["disinterested"], "1.7 19.0 7.1": ["gameplan"], "9.5 18.6 9.6": ["anyhow"], "12.2 6.2 2.0": ["trudged"], "10.2 11.0 0.3": ["evoking"], "9.3 28.7 13.1": ["mercilessly"], "-4.1 10.6 9.7": ["servicers"], "17.3 10.1 21.5": ["oiled"], "8.6 12.5 8.8": ["equator"], "5.5 7.8 17.1": ["racecourse"], "14.2 10.5 13.3": ["chimps"], "14.3 9.7 2.1": ["breathes"], "3.9 9.9 15.1": ["lager"], "8.2 7.7 0.8": ["overstate"], "17.8 11.3 5.7": ["variously"], "-3.0 9.4 6.5": ["dopamine"], "1.8 6.2 3.2": ["fluency"], "8.5 2.4 8.3": ["widescreen"], "13.3 11.2 10.6": ["butler"], "1.9 9.1 5.8": ["pedophilia"], "1.2 0.0 -0.7": ["shuttling"], "-3.0 2.3 5.5": ["reminisce"], "9.2 10.5 4.7": ["machetes"], "3.1 2.4 -6.1": ["functionalities"], "6.6 1.0 10.3": ["situ"], "-2.9 0.7 3.9": ["revoking"], "15.7 12.6 16.5": ["cauldron"], "9.7 17.8 5.4": ["pervert"], "7.0 10.5 15.4": ["donkeys"], "4.3 13.7 2.9": ["amnesia"], "4.9 -10.9 11.0": ["ng"], "17.9 5.8 12.4": ["arches"], "1.8 13.4 19.7": ["blackjack"], "-3.9 8.1 5.9": ["regression"], "-0.9 12.8 3.2": ["radicalization"], "11.2 5.8 18.6": ["tarps"], "2.6 26.8 3.9": ["mullahs"], "7.1 14.9 -1.2": ["overran"], "4.9 9.0 16.1": ["tropics"], "4.9 4.8 4.0": ["penalizing"], "14.9 9.6 14.1": ["cam"], "7.4 5.1 6.3": ["confounded", "signifiant"], "14.6 8.2 9.0": ["swiping"], "-2.6 2.7 -1.4": ["cc"], "16.7 2.9 7.8": ["skidding"], "0.8 16.8 3.6": ["converse"], "-2.6 12.2 5.9": ["rationally"], "17.2 14.1 9.7": ["linchpin"], "9.1 3.3 16.9": ["primate"], "-4.1 13.2 7.2": ["perfectionist"], "11.7 16.3 9.7": ["thrower"], "-0.2 18.1 -3.1": ["operationally"], "3.4 -2.9 3.6": ["nineties"], "-1.7 -0.4 10.4": ["panties"], "-3.3 1.1 12.6": ["equalization"], "7.3 4.0 39.9": ["cucumber"], "-4.1 2.1 3.7": ["babysitting"], "1.4 14.3 9.0": ["deuce"], "17.0 -1.6 16.6": ["fatter"], "6.1 5.2 4.8": ["deducting"], "2.3 5.2 3.3": ["philanthropists"], "6.8 8.2 6.9": ["redirecting"], "3.0 15.7 3.5": ["intimately"], "22.1 26.0 6.8": ["empires"], "15.7 3.6 5.7": ["storybook"], "3.2 0.8 14.9": ["dairies"], "2.1 6.5 5.7": ["aplomb"], "6.0 15.2 7.7": ["ineffectual"], "-3.6 7.9 10.7": ["ethnicities"], "-6.4 -0.1 13.9": ["enrollees"], "-1.2 5.8 1.6": ["differentials"], "15.5 6.7 8.6": ["wilted"], "10.8 5.7 3.8": ["booting"], "-6.5 24.8 5.2": ["disciple"], "5.5 6.4 6.6": ["councilwoman"], "10.8 15.1 13.6": ["smother"], "5.7 9.8 2.1": ["arbiter"], "5.6 7.9 -1.7": ["adulation"], "0.7 11.6 1.4": ["agnostic"], "11.4 0.1 2.4": ["derailing"], "-11.9 1.5 2.1": ["timeshare"], "7.5 4.8 10.0": ["hoot"], "9.0 7.3 5.5": ["mules"], "13.2 5.9 5.7": ["motifs"], "10.4 10.1 25.5": ["oaks"], "5.7 8.6 3.7": ["smarting"], "5.5 10.1 1.6": ["synergistic"], "-4.2 6.5 4.2": ["tailbacks"], "4.8 6.7 3.4": ["consolidations"], "11.1 13.1 15.6": ["princes"], "-6.1 12.6 3.3": ["handicaps"], "6.9 9.8 6.1": ["infrequently"], "6.4 1.4 3.0": ["ironing"], "6.3 4.8 16.1": ["hipster"], "0.8 12.6 7.1": ["hinders"], "-6.0 6.0 10.1": ["antidepressant"], "0.3 23.2 6.1": ["vindictive"], "-7.1 -7.7 4.3": ["stipends"], "2.2 -0.6 -2.9": ["petitioning"], "-3.4 1.7 5.2": ["summarizing"], "-8.7 2.7 -1.4": ["conferring"], "5.2 5.5 9.8": ["cleavage"], "1.7 12.4 6.7": ["disregarding"], "-0.9 3.5 3.1": ["snowed"], "-12.5 5.3 -0.4": ["trainings"], "7.3 12.3 -4.0": ["discreetly"], "22.2 12.9 7.2": ["symbolizing"], "-2.1 6.5 3.1": ["microbiology"], "21.0 13.6 11.7": ["nerds"], "-5.4 3.1 7.4": ["ligaments"], "17.6 19.9 16.2": ["swamps"], "8.8 -1.9 17.9": ["lids"], "3.5 6.9 2.2": ["tamper"], "18.6 11.2 11.8": ["purveyors"], "10.8 17.6 7.7": ["whore"], "-0.3 7.0 3.1": ["succinct"], "-2.1 12.9 -4.3": ["audiotape"], "-2.8 15.9 2.9": ["sufferings"], "-0.8 19.9 2.1": ["truthfully"], "-1.9 22.8 9.4": ["expendable"], "11.8 25.3 4.2": ["protectors"], "5.1 12.1 2.9": ["retooling"], "-3.1 6.9 6.0": ["cellist"], "7.8 0.8 21.6": ["buns"], "13.1 14.8 6.0": ["havens"], "3.3 7.5 12.4": ["rancor"], "17.0 6.8 11.5": ["toothless"], "5.1 -1.7 -6.4": ["inaugurating"], "-8.6 6.5 -0.3": ["candidature"], "19.3 16.0 26.5": ["watery"], "3.4 5.5 10.7": ["jovial"], "4.7 10.9 0.7": ["handhelds"], "5.0 1.7 10.5": ["mystified"], "6.6 6.6 11.0": ["decals"], "15.9 6.7 6.5": ["fro"], "2.3 7.3 2.6": ["gifting"], "-1.0 -8.8 5.8": ["webcasts"], "-5.7 12.6 6.1": ["pious"], "1.0 7.4 5.6": ["theorized"], "-3.0 5.4 32.1": ["orchids"], "9.8 5.7 6.2": ["parched"], "-1.0 6.7 14.1": ["conservancy"], "-5.5 2.0 -0.5": ["intimated"], "8.2 11.1 -1.3": ["combustible"], "-8.9 17.5 3.7": ["sergeants"], "1.1 16.5 1.0": ["imperfections"], "2.7 7.0 9.5": ["setters"], "0.0 5.5 7.0": ["judicious"], "8.7 17.0 10.5": ["harden"], "1.9 3.1 -3.5": ["accosted"], "2.7 9.5 7.9": ["transistor"], "5.3 -4.6 2.7": ["parlayed"], "-3.6 12.1 2.4": ["acclimated"], "-8.2 -1.5 -6.2": ["clarifications"], "-5.8 6.5 9.3": ["coffees"], "-0.8 12.7 7.9": ["redouble"], "4.6 20.6 10.9": ["subconscious"], "3.2 10.1 6.0": ["robs"], "4.6 3.2 4.7": ["deceleration"], "6.4 7.9 9.4": ["sorely"], "9.6 9.2 7.9": ["neural"], "8.2 -1.5 4.4": ["clippings"], "9.9 5.4 8.9": ["trampoline"], "1.9 4.8 2.5": ["endpoints"], "5.3 -5.9 0.3": ["piqued"], "-9.1 11.1 -2.4": ["undiagnosed"], "16.6 9.9 14.4": ["mojo"], "11.3 20.8 4.6": ["moron"], "-3.8 9.8 5.9": ["prudently"], "0.1 0.2 -4.5": ["penning"], "5.5 1.8 4.9": ["stagnated"], "12.1 25.1 4.1": ["taunt"], "6.1 3.7 3.5": ["ambulatory"], "-2.4 3.7 2.1": ["inconvenienced"], "11.6 6.2 -0.2": ["propels"], "10.5 7.7 4.2": ["trotting"], "5.3 12.7 2.3": ["relent"], "30.1 3.7 9.8": ["contraption"], "0.9 2.4 12.3": ["veneer"], "0.4 10.0 2.8": ["rifts"], "11.4 14.0 9.2": ["unsurprisingly"], "0.8 11.4 0.9": ["reachable"], "6.5 12.1 7.7": ["insulating"], "-2.2 2.8 8.5": ["deportations", "inspec"], "10.4 12.8 9.4": ["outdo"], "15.7 10.7 5.9": ["crushes"], "19.6 18.8 7.6": ["faraway"], "17.9 10.8 8.0": ["immortality"], "9.5 6.9 10.9": ["tasteless"], "15.6 -3.9 9.9": ["shakers"], "9.0 5.3 3.4": ["transporters"], "-5.6 13.7 -1.2": ["misinformed"], "24.4 20.2 14.5": ["winged"], "-5.3 4.8 8.5": ["biologics"], "-2.3 2.6 1.0": ["convocation"], "-0.7 4.6 6.0": ["placings"], "-5.2 3.6 -3.4": ["corroborate"], "-3.5 7.2 -1.3": ["glean"], "0.0 -3.7 7.5": ["ml"], "16.1 10.8 14.2": ["clumps"], "6.4 8.8 4.3": ["esophagus"], "10.1 8.4 9.5": ["undisturbed"], "4.8 12.8 3.8": ["blindsided"], "-3.2 0.4 1.2": ["accruing"], "0.1 7.7 4.6": ["fumed"], "10.8 5.8 7.0": ["dissected"], "5.5 12.6 -6.5": ["trashing"], "0.1 13.2 3.2": ["infer"], "14.6 4.6 6.1": ["hitched"], "19.8 9.9 12.4": ["tabletop"], "0.7 4.7 7.3": ["hundredths"], "-4.2 6.2 10.1": ["blouse"], "8.2 5.0 29.4": ["grapefruit"], "13.1 12.5 4.9": ["intently"], "22.6 17.1 5.8": ["rampaging"], "20.0 17.7 28.0": ["fairy"], "13.7 3.8 13.0": ["matriarch"], "16.2 11.7 4.0": ["censoring"], "5.4 19.5 8.1": ["sarcastically"], "-8.8 9.9 1.6": ["introspection"], "10.1 12.4 5.3": ["vistas"], "7.9 -0.2 -0.6": ["refocused"], "22.1 0.4 0.4": ["bankrolled"], "12.5 17.7 6.4": ["smuggler"], "14.9 10.0 17.4": ["crumbs"], "10.1 10.9 5.3": ["puddles"], "11.4 9.3 3.3": ["whisk"], "6.1 5.1 9.0": ["paceman"], "2.5 6.4 4.6": ["criminalize"], "9.4 15.6 7.1": ["grudgingly"], "3.6 4.6 6.5": ["sectoral"], "5.3 9.4 1.5": ["contravention"], "2.5 12.1 6.2": ["bigs"], "6.8 21.8 14.7": ["ye"], "-1.7 9.0 28.4": ["marinas"], "3.3 3.5 5.5": ["brainstorm"], "11.0 9.1 12.8": ["shipper"], "10.2 8.3 0.3": ["purports"], "6.7 -1.7 19.3": ["ponies"], "8.7 2.5 14.1": ["samba"], "3.0 6.0 5.1": ["ably"], "8.8 7.0 3.5": ["telematics"], "-0.5 17.7 12.0": ["gravely"], "5.9 8.9 6.2": ["posterity"], "12.3 13.2 -1.4": ["innovating"], "-1.6 -0.5 0.7": ["rescheduling"], "13.6 20.2 16.8": ["scum"], "15.9 -1.2 5.6": ["revives"], "7.3 16.0 9.0": ["insanely"], "0.7 18.8 2.8": ["bioterrorism"], "3.5 12.9 5.0": ["socialized"], "3.3 8.8 3.7": ["reverting"], "6.0 20.0 5.3": ["unjustly"], "10.2 10.9 3.8": ["customizing"], "13.8 2.8 -1.8": ["decrying"], "28.0 -3.4 9.0": ["risers"], "9.7 19.7 13.2": ["enslaved"], "9.3 -0.7 9.1": ["folksy"], "6.3 3.2 5.9": ["landscaped"], "13.4 12.8 1.5": ["tamed"], "7.4 15.9 6.9": ["electron"], "4.0 5.2 9.8": ["farcical"], "1.1 1.9 4.3": ["hernia"], "16.5 11.7 1.4": ["halo"], "0.5 19.7 3.7": ["embers"], "-2.6 12.7 14.5": ["seamer"], "8.5 5.0 5.4": ["lounging"], "3.9 -5.5 0.4": ["sifted"], "19.2 1.6 1.3": ["industrials"], "13.7 1.2 9.1": ["trinkets"], "5.9 0.5 10.0": ["solids"], "4.3 4.3 -1.1": ["cursory"], "14.9 8.0 26.1": ["ornamental"], "-5.9 4.9 5.9": ["byline"], "5.5 3.9 13.1": ["wiki"], "9.2 6.0 8.5": ["nerdy"], "12.2 4.1 14.4": ["crunched"], "3.8 30.8 3.8": ["appeasement"], "-0.7 9.3 14.8": ["fermentation"], "-9.8 21.4 0.2": ["declassified"], "2.8 8.6 2.4": ["consummation"], "7.6 1.7 5.2": ["emaciated"], "4.9 7.5 4.2": ["neo"], "16.6 7.4 6.8": ["outlawing"], "-2.9 6.0 -2.6": ["harmonization"], "-0.3 4.7 12.0": ["effluent"], "2.9 17.7 5.8": ["enigma"], "5.2 14.1 11.1": ["knockdown"], "-6.9 0.3 5.2": ["redshirted"], "11.4 5.4 4.3": ["supplanted"], "8.3 -0.7 6.6": ["rejuvenation"], "0.5 2.2 8.1": ["conservatory"], "6.1 8.1 2.0": ["pedaling"], "0.7 21.8 -4.1": ["brainwashed"], "14.9 6.0 9.3": ["geeky"], "-8.5 21.7 -4.7": ["interrogating"], "8.8 8.6 7.8": ["amiable"], "1.5 3.7 5.3": ["speculates"], "-5.2 4.9 9.8": ["colts"], "9.7 20.2 6.3": ["intrusions"], "6.0 17.8 -0.5": ["unrepentant"], "0.6 8.1 -0.7": ["misrepresenting"], "8.5 2.6 2.9": ["tripartite"], "11.7 14.5 6.4": ["mistaking"], "7.2 1.9 28.2": ["cheesecake"], "9.4 3.7 13.7": ["bob"], "12.7 15.3 9.8": ["ramming"], "19.8 9.6 8.2": ["decrepit"], "13.2 6.0 13.1": ["commons"], "3.8 1.9 -6.3": ["pore"], "-6.4 7.6 9.8": ["duets"], "10.2 11.6 10.1": ["subtracting"], "-4.0 6.0 8.9": ["waistband"], "0.8 8.3 11.3": ["spleen"], "9.9 6.8 32.5": ["swans"], "2.9 17.1 11.7": ["bluster"], "12.9 -0.9 1.4": ["toyed"], "-0.4 8.1 42.2": ["overfishing"], "2.9 22.4 11.1": ["paintball"], "8.6 14.4 -1.3": ["ur"], "15.5 9.3 13.8": ["oddball"], "3.2 0.0 3.5": ["ingest"], "6.9 -1.3 0.0": ["conforms"], "0.7 3.0 3.8": ["duplicates"], "7.0 17.6 14.5": ["mobsters"], "7.9 4.9 11.1": ["monorail"], "2.2 4.8 13.7": ["saucepan"], "12.5 8.8 27.7": ["chestnut"], "10.1 1.9 6.2": ["lapping"], "2.5 0.1 -1.7": ["spotless"], "12.8 9.9 6.4": ["napping"], "3.3 17.7 16.9": ["propagation"], "0.3 7.6 5.3": ["rd"], "21.2 4.9 13.0": ["chubby"], "11.9 -1.9 8.7": ["blowouts"], "10.0 15.2 9.0": ["ferret"], "15.0 -7.2 5.7": ["wrangle"], "-5.2 2.8 8.1": ["tamoxifen"], "8.0 5.6 11.7": ["rollicking"], "4.0 40.0 0.2": ["cowards"], "5.8 13.4 4.7": ["uttering"], "5.2 6.4 4.2": ["launder"], "11.5 12.2 23.5": ["lemons"], "8.0 9.9 15.1": ["ness"], "2.0 10.0 3.5": ["invigorating"], "3.6 9.6 15.2": ["toolbox"], "17.4 6.8 9.9": ["sofas"], "-1.1 -2.1 -2.0": ["micrograms"], "4.6 -0.1 8.1": ["lotion"], "21.9 -0.6 7.8": ["dangled"], "6.6 2.2 5.8": ["flaring"], "7.2 7.1 7.1": ["giggles"], "12.9 17.1 0.7": ["ridding"], "8.9 -1.6 5.5": ["skirted"], "8.1 2.2 -0.4": ["greenfield"], "6.5 12.0 2.3": ["unabashed"], "-1.7 5.2 22.2": ["oceanfront"], "18.0 9.1 15.2": ["protruding"], "-0.3 14.5 7.4": ["orthodoxy"], "-3.7 14.4 4.1": ["pluralism"], "8.2 12.5 -1.5": ["indistinguishable"], "5.2 6.4 12.0": ["sighs"], "8.0 10.6 10.0": ["hollering"], "8.7 -8.3 3.2": ["sedate"], "12.8 18.0 11.5": ["manly"], "-1.2 4.9 -0.9": ["aspired"], "1.4 -1.0 9.9": ["recessed"], "19.3 15.5 20.0": ["vultures"], "9.8 -1.2 22.5": ["freezers"], "-4.9 1.8 2.3": ["regimens"], "0.3 20.3 12.5": ["helplessness"], "9.8 7.2 13.4": ["latex"], "-5.9 5.5 8.2": ["cardholder"], "10.5 14.1 8.2": ["screwing"], "2.8 14.0 4.7": ["lynching"], "-0.0 2.2 2.4": ["delving"], "3.5 9.2 7.8": ["caskets"], "6.1 9.0 8.8": ["populous"], "-3.5 5.1 14.4": ["blazer"], "8.7 16.8 2.6": ["graphically"], "13.0 22.3 13.8": ["superstition"], "11.0 4.8 3.0": ["reconstituted"], "-8.9 2.7 11.5": ["umpiring"], "-10.1 7.1 2.6": ["negotiable"], "3.0 5.7 5.4": ["remedied"], "9.4 9.1 5.3": ["trickier"], "2.9 6.9 7.2": ["downpours"], "1.2 -7.0 2.8": ["unconvinced"], "14.1 15.0 10.9": ["darting"], "3.9 6.4 12.9": ["stringer"], "12.7 -1.4 9.2": ["ma"], "14.3 20.8 1.5": ["salvo"], "11.0 0.7 18.4": ["skim"], "0.1 -0.3 -0.3": ["prepayment"], "3.1 17.5 12.5": ["pollutant"], "7.9 21.2 1.2": ["instantaneously"], "7.6 9.3 5.5": ["enthralling"], "19.2 17.8 21.6": ["suckers"], "7.7 3.7 10.9": ["slowdowns"], "5.8 18.5 2.9": ["prophets"], "0.7 2.2 -0.8": ["affording"], "8.5 9.7 29.4": ["fudge"], "-0.3 0.4 11.8": ["traceability"], "6.2 12.2 5.5": ["perpetuating"], "13.9 5.8 14.3": ["snarled"], "-0.6 4.1 12.7": ["desalination"], "1.7 9.8 1.4": ["penal"], "14.0 24.5 27.6": ["crows"], "11.2 10.1 11.1": ["grove"], "0.0 2.4 69.0": ["scallops"], "6.4 4.5 4.0": ["faze"], "8.6 8.4 15.5": ["shrinkage"], "4.7 1.5 0.8": ["indemnity"], "2.5 2.7 5.6": ["heeding"], "8.2 7.9 3.9": ["holing"], "15.3 1.5 0.7": ["heralds"], "1.1 5.6 5.9": ["formatting"], "5.6 9.9 0.8": ["cot"], "5.4 7.6 9.7": ["fraternities"], "2.2 13.8 11.3": ["autopilot"], "18.0 5.8 7.2": ["reappeared"], "2.7 8.1 8.7": ["treasuries"], "1.8 5.0 4.3": ["sweats"], "9.1 24.5 -0.2": ["demonize"], "0.8 1.9 -1.2": ["cassette"], "22.0 10.5 11.2": ["skyward"], "3.6 -1.5 14.2": ["curbside"], "11.7 6.8 11.5": ["unseemly"], "-2.3 18.0 2.5": ["endangers"], "-1.2 12.4 3.0": ["vitriol"], "6.1 3.0 8.8": ["collared"], "10.7 6.2 5.2": ["stuns"], "11.7 17.9 2.3": ["insignia"], "-0.3 0.9 9.3": ["stabbings"], "8.1 23.6 5.9": ["dictatorships"], "6.3 11.6 1.7": ["groundless"], "1.9 6.7 8.8": ["bangs"], "2.6 11.1 0.2": ["chargesheet"], "10.6 -3.8 6.0": ["midtown"], "16.6 15.3 10.5": ["wand"], "0.5 14.9 8.1": ["straying"], "9.2 0.6 12.9": ["luge"], "-4.0 8.8 -5.1": ["commendation"], "1.6 7.8 8.3": ["outbuildings"], "-8.0 7.4 2.7": ["introspective"], "17.5 2.9 -1.7": ["merges"], "-9.6 5.5 7.9": ["uncommitted"], "9.4 4.8 -2.4": ["sited"], "16.6 15.9 5.7": ["mountaintop"], "8.2 9.8 4.9": ["canister"], "2.8 15.1 -0.0": ["desecration"], "16.1 -3.1 0.5": ["snaked"], "28.8 15.7 20.3": ["tentacles"], "3.8 4.6 36.4": ["pears"], "13.2 7.1 7.6": ["stymie"], "5.0 -1.7 -1.9": ["gagged"], "12.8 10.2 3.9": ["feverishly"], "3.0 28.5 8.9": ["righteousness"], "-0.0 15.0 8.6": ["baserunner"], "11.4 7.4 10.9": ["plodding"], "6.6 5.6 1.8": ["funders"], "3.0 6.0 9.6": ["grasslands"], "2.8 20.5 5.6": ["unpopularity"], "0.3 11.3 1.3": ["incited"], "11.2 15.3 10.9": ["grunt"], "3.9 9.4 2.6": ["diluting"], "6.4 10.1 3.5": ["veils"], "5.3 25.7 11.1": ["delusion"], "3.9 9.3 8.6": ["commune"], "15.9 3.7 5.5": ["beckons"], "17.9 13.3 1.2": ["sapping"], "-5.1 6.2 5.6": ["noncompliance"], "4.0 1.9 -5.8": ["debunked"], "5.2 6.1 5.9": ["dons"], "1.0 17.4 11.9": ["barked"], "-8.7 0.7 9.7": ["scholastic"], "4.8 6.9 3.2": ["uncovers"], "2.8 8.9 3.7": ["outshooting", "bler"], "-1.5 2.1 14.2": ["tailings"], "1.6 2.3 3.5": ["cataloged"], "4.3 22.6 1.6": ["gallant"], "13.8 6.9 4.3": ["revving"], "-5.0 4.2 -1.1": ["seatbelts"], "2.8 8.0 -1.5": ["suffocation"], "-3.4 10.8 -7.0": ["recharged"], "-6.1 8.7 -1.0": ["instilling"], "21.2 25.9 5.1": ["impenetrable"], "15.4 -2.9 7.6": ["overturns"], "-0.8 11.8 5.0": ["teeing"], "-0.4 8.4 5.6": ["flyhalf"], "4.0 -4.4 8.1": ["pa"], "7.0 5.6 6.8": ["underpinnings"], "0.6 8.9 10.4": ["graze"], "-1.2 9.6 11.7": ["uptight"], "-3.6 14.4 9.0": ["demarcation"], "2.4 13.3 -1.8": ["outed"], "9.3 14.2 10.3": ["fellas"], "6.4 12.3 7.1": ["rainstorm"], "9.7 8.7 6.2": ["snoring"], "-0.2 6.6 3.7": ["spillover"], "12.5 13.4 2.0": ["exponential"], "15.1 10.3 11.8": ["pinching"], "2.4 9.0 11.0": ["valet"], "7.5 10.6 5.4": ["symmetry"], "5.5 1.7 7.3": ["ranching"], "3.7 21.6 9.1": ["embolden"], "16.3 6.6 16.5": ["costumed"], "13.0 20.2 8.5": ["cruelly"], "17.4 15.2 10.6": ["cosmos"], "-9.1 10.7 4.6": ["understandings"], "7.3 17.3 1.6": ["waver"], "0.3 9.9 4.9": ["socialization"], "0.9 9.7 5.5": ["maximized"], "-0.2 9.0 6.8": ["appendix"], "4.4 11.7 51.7": ["shad"], "12.9 19.4 10.0": ["motionless"], "-0.6 6.9 37.3": ["parsley"], "1.4 8.9 10.3": ["panchayat"], "5.3 18.5 14.3": ["insecticide"], "12.0 5.4 30.8": ["taco"], "10.2 5.7 22.5": ["chuck"], "5.1 4.2 15.3": ["burgundy"], "20.2 4.6 13.3": ["wobble"], "10.8 8.2 0.7": ["reinvention"], "8.1 8.4 20.2": ["bouncers"], "1.0 12.0 7.1": ["deteriorates"], "-4.0 10.8 7.0": ["closers"], "0.6 -1.4 1.8": ["delves"], "8.3 -4.2 4.8": ["mar"], "1.8 13.9 3.7": ["implausible"], "5.5 22.6 9.0": ["earthly"], "5.9 8.7 20.1": ["thawing"], "9.1 4.1 3.0": ["crescendo"], "9.6 14.9 4.5": ["bane"], "16.1 -1.1 14.8": ["fiesta"], "5.4 0.3 17.7": ["sawmill"], "5.4 -0.5 19.4": ["muffins"], "-2.4 4.7 8.5": ["modems"], "16.3 5.2 1.2": ["feverish"], "4.5 6.3 0.5": ["frontrunners"], "21.0 3.0 8.4": ["riser"], "8.7 15.6 7.8": ["adoration"], "10.5 5.6 11.9": ["mainstays"], "0.3 6.8 -3.7": ["junctions"], "2.5 4.3 8.4": ["stabilizes"], "15.1 5.6 6.7": ["puffing"], "6.3 9.2 9.3": ["moan"], "-6.2 7.1 6.2": ["liturgy"], "-2.7 1.1 -1.3": ["undrafted"], "-0.7 11.2 2.5": ["functionaries"], "6.7 3.3 6.2": ["taut"], "10.6 10.3 5.9": ["knelt"], "7.1 8.2 10.2": ["org"], "-0.8 3.0 0.5": ["heckled"], "0.8 13.0 5.3": ["retelling"], "7.2 21.2 8.0": ["flinch"], "6.6 15.8 9.2": ["mouthed"], "11.9 13.5 3.1": ["glancing"], "7.6 5.2 37.5": ["celery"], "18.5 8.7 9.2": ["steelmaker"], "17.8 8.8 1.5": ["cacophony"], "12.6 23.0 11.0": ["dungeon"], "-0.4 19.2 5.6": ["tackler"], "18.2 8.8 22.4": ["poop"], "7.8 4.0 5.1": ["hookup"], "2.2 11.2 3.8": ["inquisitive"], "8.0 8.9 0.2": ["spokespeople", "pulsation"], "-0.2 8.4 0.4": ["safeguarded"], "11.9 15.2 2.8": ["beheadings"], "6.4 3.5 7.8": ["mod"], "1.0 8.1 13.5": ["dispersal", "reveries"], "-7.1 6.1 9.0": ["unscripted", "overclock"], "-1.4 5.9 6.6": ["pacer"], "3.1 15.2 6.6": ["xenophobia"], "-0.4 7.6 1.8": ["beautify"], "9.5 1.7 8.1": ["aplenty"], "2.9 11.3 0.8": ["taker"], "3.5 5.6 -7.6": ["congratulatory"], "-0.8 3.5 6.8": ["tome"], "18.6 5.9 5.0": ["marvels"], "7.1 27.2 15.9": ["combos"], "17.1 22.7 -0.5": ["electromagnetic"], "-2.0 -3.0 6.5": ["recur"], "17.2 3.2 5.7": ["barcode"], "11.6 9.2 11.2": ["vagaries"], "7.2 9.5 17.3": ["loggers"], "5.2 8.3 14.1": ["gutting"], "5.7 2.8 16.1": ["baseballs"], "10.2 7.0 3.5": ["toothbrush"], "-6.9 19.3 5.7": ["reservist"], "0.9 7.0 4.0": ["mailer"], "3.4 2.4 14.8": ["sustainably"], "4.9 14.4 4.7": ["sneezing"], "7.7 8.7 14.5": ["wintry"], "4.6 14.5 3.2": ["patting"], "14.8 19.2 15.2": ["hound"], "1.8 21.8 0.4": ["unworthy"], "2.6 13.6 13.8": ["savoring"], "2.1 10.7 2.0": ["perpetuated"], "9.3 13.3 8.7": ["derision"], "0.7 6.3 8.9": ["councilmen"], "-8.6 4.6 4.9": ["monologues"], "4.6 9.5 4.2": ["reincarnation"], "0.3 -3.1 7.2": ["pampering"], "-1.8 13.2 6.9": ["monasteries"], "17.4 13.9 12.5": ["puddle"], "-10.3 6.2 -1.8": ["abstaining"], "7.9 9.2 9.2": ["straddle"], "-2.8 12.4 4.7": ["booksellers"], "5.5 10.7 5.9": ["reveling"], "-0.8 5.7 -0.2": ["aspirational"], "15.1 15.9 6.8": ["adoring"], "4.4 7.3 15.1": ["grandparent"], "3.5 1.9 12.9": ["dioxin"], "-1.1 17.6 4.3": ["unimportant"], "3.5 20.4 2.3": ["relaying"], "7.1 14.0 10.6": ["breezes"], "11.2 9.0 4.7": ["wring"], "6.7 13.8 2.6": ["stairway"], "-6.0 -0.5 3.4": ["skincare"], "7.4 13.0 16.5": ["mobster"], "-6.7 6.5 11.3": ["realtors"], "6.8 22.8 2.0": ["regrouping"], "7.2 10.0 4.0": ["clipboard"], "0.3 -3.9 -2.2": ["embezzled"], "6.6 1.9 8.2": ["wrestles"], "0.6 10.4 -2.3": ["disprove"], "8.3 3.3 5.3": ["scrubbing"], "7.7 24.4 4.4": ["irritant"], "2.4 11.4 -2.7": ["unseated"], "7.2 4.5 6.6": ["untitled"], "16.3 7.1 18.8": ["cubic"], "5.1 7.3 8.2": ["unreasonably"], "12.9 7.5 -5.4": ["blared"], "0.2 7.7 11.4": ["dowry"], "5.4 18.0 6.9": ["fittest"], "16.7 4.7 6.2": ["cushioned"], "7.3 17.1 0.3": ["bearer"], "9.3 8.2 11.5": ["rearrange"], "-0.4 18.3 5.6": ["electioneering"], "6.9 -0.7 10.9": ["skimmed"], "-5.4 16.8 0.2": ["inspirations"], "3.8 3.4 9.7": ["hangers"], "5.7 6.2 15.9": ["delightfully"], "3.7 11.1 5.8": ["schoolhouse"], "11.1 6.1 4.7": ["seizes"], "9.0 6.1 -4.8": ["infringes"], "2.4 3.7 11.1": ["wristband"], "-9.6 5.7 5.8": ["phrasing"], "-3.8 8.6 1.4": ["vocally"], "10.8 4.5 8.4": ["ratcheting"], "7.1 19.2 22.0": ["crewmen"], "13.6 -0.6 8.9": ["scruffy"], "15.8 -0.9 3.4": ["reignite"], "0.8 -2.0 7.8": ["barbershop"], "5.8 3.8 9.0": ["bobsled"], "4.2 0.7 15.8": ["bakers"], "4.4 0.2 6.2": ["slippage"], "19.8 17.3 8.0": ["pummeling"], "8.5 6.3 5.4": ["reconfigure"], "2.7 16.6 -2.3": ["irritate"], "9.5 30.2 10.4": ["devious"], "7.0 0.7 7.8": ["belied"], "7.9 11.3 -0.1": ["herded"], "14.8 26.5 10.1": ["capitalists"], "7.0 10.5 14.9": ["gums"], "12.9 18.0 9.9": ["ridges"], "-5.3 -4.0 1.5": ["fellowships"], "9.1 8.7 5.7": ["overheads"], "21.5 16.2 8.4": ["ugliest"], "-0.5 0.9 17.2": ["carat"], "9.9 4.0 8.3": ["dimming"], "5.5 8.8 8.2": ["labors"], "-4.3 9.5 8.3": ["absconding"], "0.6 4.9 0.8": ["nanometers"], "8.4 14.5 8.3": ["lightening"], "-1.2 -0.4 18.4": ["tastings"], "13.9 21.7 12.7": ["verb"], "9.0 17.5 0.8": ["summoning"], "3.6 13.6 11.4": ["insecurities"], "2.2 17.1 9.0": ["tacit"], "-2.2 4.2 7.9": ["prelims"], "1.6 22.5 1.2": ["aircrafts"], "-2.9 16.0 4.3": ["ostracized"], "8.9 6.9 17.3": ["planks"], "1.6 6.7 8.6": ["subtract"], "19.9 19.3 17.1": ["eyeball"], "7.9 6.8 14.2": ["florist"], "8.0 3.3 8.8": ["seedy"], "9.1 5.0 1.2": ["retrofitted"], "-8.4 2.1 22.6": ["yearling"], "4.0 6.6 16.5": ["layering"], "2.5 4.0 3.5": ["scribbled"], "-6.8 3.6 -5.2": ["differentiates"], "1.6 14.4 6.1": ["shorting"], "1.2 -3.8 11.2": ["reauthorization"], "5.3 4.7 30.9": ["pickles"], "6.6 3.4 2.6": ["swished"], "32.6 7.9 -0.4": ["baron"], "1.7 8.6 10.3": ["dayer"], "2.1 1.5 26.4": ["canning"], "8.4 13.2 5.1": ["insular"], "-0.3 14.2 7.8": ["obeyed"], "16.8 12.9 11.3": ["thud"], "3.2 15.3 6.8": ["dichotomy"], "12.0 8.8 7.0": ["lite"], "6.0 9.9 -2.4": ["firebrand"], "13.6 3.6 5.7": ["trademarked"], "23.0 8.2 2.2": ["supremo"], "-1.7 7.0 9.4": ["snowing"], "5.1 10.6 6.3": ["duds"], "5.9 23.5 19.4": ["microorganisms"], "2.5 1.2 4.4": ["streetlights"], "6.4 8.1 6.5": ["elation"], "-2.4 7.6 6.5": ["freelancers"], "1.4 8.4 17.4": ["freshest"], "0.9 5.4 2.4": ["creditworthiness"], "-6.4 1.1 7.3": ["choreographers"], "2.3 8.9 5.3": ["carelessness"], "11.7 11.4 4.3": ["banish"], "12.5 2.1 0.2": ["permeated"], "2.6 13.0 15.2": ["standup"], "14.1 12.9 12.6": ["duke"], "5.4 -1.2 2.3": ["latched"], "12.3 15.3 0.4": ["henceforth"], "11.5 2.6 1.4": ["outbid"], "6.8 13.7 13.1": ["visor"], "12.6 6.4 11.9": ["confounding"], "24.1 9.4 16.7": ["munching"], "-1.3 12.2 35.6": ["crappie"], "1.8 7.8 5.2": ["idiosyncratic"], "0.1 3.0 2.1": ["interprets"], "4.9 9.9 5.8": ["unneeded"], "4.9 8.9 10.2": ["earnestly"], "8.1 6.5 5.7": ["preying"], "11.9 -0.8 6.8": ["brim"], "21.0 11.3 9.1": ["flapping"], "5.2 9.6 12.8": ["retarded"], "12.5 13.1 9.1": ["warp"], "5.5 9.6 10.8": ["knob"], "-0.5 20.2 8.0": ["obeying"], "1.3 8.5 2.8": ["sanitized"], "6.5 0.6 7.7": ["unmoved"], "-7.0 3.0 6.9": ["weblog"], "-2.9 0.1 2.7": ["podcasting"], "-3.5 10.7 2.9": ["stylistic"], "-1.3 5.7 7.5": ["dissertation"], "7.5 10.6 -2.2": ["fervently"], "3.9 10.6 4.6": ["unfairness"], "-2.0 8.0 10.4": ["downforce"], "5.1 11.0 24.2": ["barbeque"], "11.6 3.7 9.9": ["welder"], "-0.1 10.2 -3.5": ["intercom"], "-1.0 13.7 6.6": ["wavelengths"], "4.9 0.8 4.0": ["scrubs"], "5.2 7.6 5.5": ["persisting"], "-4.7 5.2 19.0": ["alfalfa"], "13.1 1.9 15.6": ["hauls"], "-1.5 13.2 1.0": ["radiological"], "6.3 27.2 4.6": ["preemptive"], "0.8 8.3 6.2": ["convinces", "subplot"], "4.0 9.4 -0.0": ["devalue"], "4.0 6.6 6.1": ["abate"], "11.1 10.8 5.4": ["silhouettes"], "7.3 9.5 11.1": ["drunks"], "15.8 15.3 4.8": ["flicking"], "0.9 2.2 4.0": ["trombone"], "5.2 4.3 6.4": ["cashflow"], "0.9 23.1 3.8": ["multiplier"], "8.5 8.2 16.1": ["backhoe"], "1.7 11.1 10.7": ["effecting"], "3.4 9.7 0.5": ["reconstructing"], "16.9 18.3 17.4": ["chainsaw"], "1.3 -1.2 3.1": ["alums"], "13.6 8.1 19.6": ["forks"], "-2.3 15.7 3.8": ["succinctly"], "-7.6 1.1 -1.9": ["detoured"], "-10.4 7.5 7.3": ["indiscipline"], "0.3 5.1 9.6": ["clothed"], "8.7 1.8 9.6": ["waterlogged"], "6.3 5.4 6.7": ["genomes"], "0.7 -2.3 -0.4": ["gels"], "2.5 5.5 -0.9": ["blockages"], "5.4 6.2 9.5": ["subgroup"], "-3.0 -4.3 4.4": ["guardianship"], "-9.5 8.2 2.5": ["unanimity"], "1.1 11.4 11.8": ["orgasm"], "17.1 4.6 11.4": ["offloading"], "11.5 6.7 5.4": ["aggregator"], "3.9 3.5 -3.8": ["solidifies"], "3.2 12.2 19.4": ["prune"], "-1.3 10.0 4.5": ["talkative"], "-2.7 -1.5 19.9": ["rafting"], "14.9 18.8 7.7": ["rescuer"], "15.7 10.5 8.6": ["ahem"], "19.2 7.8 17.8": ["lantern"], "13.2 3.9 12.5": ["zany"], "26.5 2.2 7.2": ["tycoons"], "12.1 16.3 10.9": ["memorably"], "-7.4 16.7 1.9": ["judgmental"], "5.6 13.1 6.3": ["slugfest"], "-2.7 13.4 0.7": ["deactivated"], "23.7 14.5 41.9": ["snails"], "6.1 9.5 4.4": ["constructs"], "1.5 4.1 5.7": ["inheriting"], "-10.6 22.1 3.5": ["ideologically"], "16.1 3.6 11.4": ["skids"], "22.7 9.4 4.1": ["engulfing"], "-2.6 11.5 4.5": ["underutilized"], "-5.3 5.5 7.7": ["parolees"], "0.6 6.6 6.1": ["oldies"], "4.4 7.2 19.5": ["caramel"], "10.2 11.6 25.4": ["delectable"], "1.2 7.4 1.1": ["arterial"], "3.7 8.1 37.3": ["walnuts"], "5.5 5.2 1.3": ["tweens"], "1.9 13.3 3.0": ["evangelism"], "6.9 8.2 4.6": ["soiled"], "-4.7 10.1 14.5": ["ridings"], "1.6 10.3 10.8": ["biologically"], "12.5 0.1 3.5": ["strutting"], "1.7 0.8 5.1": ["tolling"], "-2.1 20.5 6.0": ["dictatorial"], "5.5 1.3 0.5": ["cf"], "6.1 12.4 1.3": ["pathological"], "8.9 21.4 5.9": ["passively"], "12.2 10.1 9.1": ["flagpole"], "-5.7 15.8 6.8": ["nonproliferation"], "14.8 -0.1 23.6": ["fatty"], "2.6 4.1 34.2": ["cucumbers"], "10.2 12.4 12.2": ["imperiled"], "19.8 2.7 -0.5": ["overcharging"], "-3.0 12.8 9.8": ["condescending"], "12.1 11.0 13.5": ["chimpanzee"], "16.3 11.5 8.5": ["caving"], "3.2 8.5 2.1": ["endzone"], "2.7 16.1 6.9": ["suspecting"], "1.8 7.2 4.1": ["misread"], "1.2 2.3 9.0": ["guidebook"], "13.4 10.7 5.8": ["severing"], "-7.3 8.4 5.1": ["hydration"], "8.2 7.3 9.1": ["cabbie"], "7.8 17.5 11.8": ["crotch"], "7.9 1.2 10.6": ["bioscience"], "8.8 7.3 11.7": ["hobbling", "permissioning"], "7.4 12.1 6.5": ["superfluous"], "-3.9 6.9 6.9": ["guesthouse"], "-2.0 -1.8 -1.8": ["misappropriated"], "1.7 8.6 13.0": ["syphilis"], "3.2 8.2 4.5": ["airflow"], "4.6 8.0 6.3": ["preponderance"], "1.1 16.2 11.0": ["justifications"], "16.6 18.6 11.7": ["majesty"], "0.3 7.9 13.9": ["rinks"], "10.8 12.6 4.6": ["wanders"], "5.3 15.5 -0.3": ["coerce"], "2.5 8.0 12.7": ["rarer"], "13.0 16.6 9.4": ["craters"], "-5.2 -1.0 -0.9": ["summing"], "6.1 5.3 11.0": ["vertebrae"], "2.2 6.1 7.3": ["fabricate"], "1.9 5.2 12.6": ["dresser"], "18.5 19.5 10.6": ["lords"], "2.8 7.3 -1.4": ["redeemable"], "1.1 4.6 10.6": ["carer", "jdy"], "10.0 -1.1 23.1": ["mahogany"], "-0.8 2.7 5.1": ["reminiscing"], "0.7 1.1 11.8": ["burlesque"], "4.2 8.2 13.8": ["thanksgiving"], "9.1 12.6 6.6": ["checkers"], "0.6 6.9 3.1": ["anguished"], "3.9 10.3 13.5": ["southerners"], "11.8 5.9 2.0": ["siting"], "6.7 16.1 6.0": ["antithesis"], "1.8 13.9 4.6": ["polity"], "9.4 20.9 5.2": ["unyielding"], "12.2 6.8 8.3": ["footballs"], "6.8 -4.0 13.9": ["mo"], "4.3 1.5 2.8": ["sidetracked"], "2.3 9.9 6.5": ["serviceable"], "1.8 9.6 15.4": ["sledding"], "1.1 2.0 6.7": ["deans"], "-9.9 12.8 -2.2": ["observant"], "0.2 14.7 0.9": ["grudges"], "-5.3 11.5 8.0": ["cinematographer"], "7.0 9.1 3.6": ["bandaged"], "6.9 3.5 20.6": ["bagel"], "1.5 3.8 2.4": ["resuscitation"], "11.9 3.9 4.1": ["injunctions"], "5.3 5.0 7.7": ["harried"], "6.0 21.4 23.5": ["colonists"], "15.2 4.4 4.9": ["riveted"], "8.6 8.4 12.1": ["welded"], "3.5 8.8 5.9": ["uneasiness"], "2.2 3.7 13.4": ["canoeing"], "-1.6 2.9 -3.8": ["censured"], "9.9 9.7 2.3": ["supplant"], "5.1 13.6 -2.5": ["disparaging"], "7.6 17.7 1.1": ["abetted"], "14.5 -6.2 1.4": ["mushroomed"], "-4.8 20.1 11.2": ["guardsmen"], "9.1 11.9 4.8": ["crucifixion"], "8.4 11.2 4.4": ["proliferate"], "0.4 17.8 1.7": ["notional"], "12.6 10.8 15.5": ["meadow"], "-5.7 9.8 28.0": ["boater"], "10.8 -1.1 8.0": ["bikinis"], "9.9 8.2 11.9": ["oilfields"], "18.1 9.1 8.0": ["panoramic"], "1.9 12.2 6.2": ["philosophers"], "4.7 6.3 8.3": ["captions"], "-10.4 5.0 6.4": ["thirties"], "10.5 11.2 -2.6": ["withstanding"], "10.1 8.6 2.3": ["upheavals"], "-2.5 8.1 23.0": ["voyages"], "10.3 8.1 9.3": ["overcapacity"], "4.9 10.3 2.1": ["downsides"], "25.5 15.9 6.7": ["omnipresent"], "1.5 10.3 5.8": ["dumbfounded"], "-0.8 14.1 5.5": ["faucet"], "19.0 10.7 9.1": ["tiniest"], "1.0 7.6 4.3": ["substations"], "5.0 22.0 16.8": ["euphemism"], "5.6 7.0 -0.1": ["repositories"], "5.8 6.3 6.7": ["indignant"], "5.2 -0.6 18.9": ["pizzeria"], "12.0 11.7 13.4": ["crimson"], "-0.0 9.3 6.4": ["kinship"], "6.0 6.3 4.8": ["clot"], "2.1 4.7 9.3": ["nasal"], "5.7 10.3 3.2": ["atone"], "2.0 9.8 4.5": ["schism"], "12.0 4.2 3.8": ["adhesives"], "-0.4 2.0 8.0": ["manganese"], "1.3 6.2 13.6": ["neurotic"], "9.3 9.3 9.0": ["trance"], "8.7 9.5 3.3": ["dissimilar"], "0.5 -2.0 -1.8": ["refundable"], "2.0 -1.3 -2.6": ["integrations"], "-2.7 3.0 13.6": ["dispensary"], "7.5 36.8 4.1": ["tyrants"], "0.0 15.6 5.8": ["bourgeois"], "3.7 2.1 8.4": ["bummed"], "3.5 8.9 14.6": ["woodlands"], "13.1 0.4 18.4": ["poached"], "11.2 19.2 -3.7": ["covertly"], "11.6 2.4 8.0": ["plumbers"], "7.3 4.5 62.5": ["herring"], "-1.4 3.2 10.1": ["artistically"], "1.6 21.5 6.3": ["bigoted"], "5.0 12.1 11.4": ["populism"], "7.8 -0.7 4.3": ["sweeteners"], "-0.8 1.4 3.1": ["renal"], "-0.8 4.9 5.6": ["exclusions"], "20.4 12.8 11.3": ["denizens"], "5.8 7.2 3.0": ["figurehead"], "1.8 2.5 5.9": ["grumbled"], "-3.7 -2.4 10.4": ["bungalows"], "5.0 1.2 -2.8": ["telemedicine"], "9.7 -5.7 1.0": ["mulled"], "-10.7 3.4 -1.4": ["lucid"], "0.5 0.0 2.8": ["supplementing"], "-0.1 6.7 19.9": ["vegetarians"], "14.2 7.3 3.8": ["pantheon"], "1.8 33.9 -1.0": ["jihadi"], "9.1 16.9 12.6": ["botnet"], "3.3 7.3 2.3": ["decoding"], "3.0 6.4 3.8": ["afresh"], "-2.8 13.1 8.7": ["jurisdictional"], "8.6 -2.5 -0.3": ["reassurances"], "-4.2 6.0 11.6": ["spillway"], "5.3 22.0 6.5": ["prophecy"], "4.9 17.6 18.4": ["ensues"], "24.5 22.0 10.1": ["swarms"], "-4.9 12.4 3.6": ["repetitions"], "-1.1 12.0 10.5": ["pained"], "-3.9 8.8 8.7": ["nonleague"], "8.5 2.3 10.5": ["smoothing"], "7.8 22.0 6.9": ["emptiness"], "7.3 9.0 0.9": ["stretchers"], "-5.2 17.5 4.8": ["interagency"], "7.9 3.0 2.1": ["kilowatt"], "13.3 4.8 9.7": ["superlative"], "7.4 9.8 7.9": ["traditionalists"], "5.4 4.3 18.3": ["vases"], "5.0 6.1 8.9": ["atherosclerosis"], "12.8 1.8 5.1": ["nosedive"], "14.8 6.0 5.1": ["segmented"], "5.9 3.4 4.8": ["compress"], "-4.2 13.7 13.7": ["handcuff"], "-6.8 4.6 1.1": ["unavailability"], "1.8 17.0 13.4": ["crewmembers"], "0.5 6.2 -2.1": ["unreleased"], "-12.0 5.1 11.0": ["sedation"], "8.1 5.1 5.4": ["clinches"], "2.3 26.6 7.7": ["fundamentalism"], "-4.3 10.1 7.5": ["spontaneity"], "5.6 7.7 1.1": ["gripes"], "-1.0 12.4 8.6": ["endings"], "-3.9 -2.4 10.3": ["midrange"], "20.3 1.5 9.0": ["puffed"], "5.7 2.3 3.2": ["lumped"], "19.7 20.0 9.5": ["enchanted"], "8.0 4.7 -0.3": ["liberalized"], "2.5 14.5 6.9": ["preset"], "-8.1 18.6 7.6": ["unclassified"], "3.6 15.5 4.0": ["caches"], "8.9 13.4 6.9": ["infects"], "8.9 8.0 3.9": ["hardball"], "9.5 7.0 -0.2": ["inhaling"], "12.6 16.3 9.6": ["titular"], "-3.9 6.6 7.3": ["driest"], "2.1 8.1 8.4": ["ballplayer"], "14.5 9.9 -0.2": ["deflating"], "0.5 4.3 26.0": ["kayaks"], "10.7 4.2 14.2": ["promenade"], "1.8 7.6 3.1": ["amortized"], "10.9 20.5 5.4": ["sabotaging"], "12.6 2.7 12.9": ["microchips"], "1.6 15.0 0.7": ["adaptability"], "9.6 19.7 1.7": ["masterminds"], "6.5 9.0 2.7": ["psyched"], "2.7 12.0 2.5": ["stablemate"], "17.3 5.8 -2.0": ["transporter"], "3.6 8.5 1.8": ["heartbreaker"], "-4.0 23.8 7.0": ["doctrines"], "5.0 4.1 4.4": ["proofing"], "3.3 2.0 -3.0": ["dedicates"], "6.2 5.8 1.3": ["mugged"], "-0.8 10.5 9.8": ["sportswriter"], "7.8 18.8 10.9": ["ache"], "-0.7 15.4 3.0": ["contemplation"], "-4.3 7.2 10.6": ["rebroadcast"], "13.5 12.2 5.5": ["unwitting"], "-0.8 4.5 5.9": ["wedlock"], "18.5 19.2 12.8": ["sledgehammer"], "9.0 6.5 4.9": ["unsupported"], "7.1 5.2 -0.6": ["liberalize"], "14.2 10.8 11.0": ["dismembered"], "0.5 19.6 -0.3": ["unguarded"], "7.2 12.8 0.8": ["personified"], "2.0 3.9 4.1": ["romances"], "1.1 15.7 5.0": ["braving"], "-0.8 5.6 9.3": ["assemblyman"], "2.2 3.5 13.1": ["graphite"], "0.0 13.9 4.1": ["punishes"], "6.4 9.7 -2.1": ["infringements"], "1.6 6.5 -0.5": ["underpass"], "16.7 16.3 14.8": ["paw"], "15.3 2.7 6.7": ["flexed"], "7.9 7.3 13.0": ["reproducing"], "0.0 6.9 13.8": ["liberally"], "-7.2 5.3 14.3": ["pseudoephedrine"], "13.9 8.3 5.1": ["peep"], "6.5 8.1 1.9": ["godsend"], "-2.2 12.2 -2.5": ["endeavored"], "15.2 18.2 11.3": ["castles"], "-15.8 2.4 17.2": ["carryover"], "6.7 8.8 7.8": ["shrill"], "6.9 7.9 2.8": ["consulates"], "21.2 3.4 14.3": ["roiling"], "-4.8 -2.6 11.6": ["repaving"], "28.4 26.0 4.0": ["faceless"], "10.8 15.7 -1.0": ["sheik"], "0.8 4.7 0.9": ["sympathized"], "7.6 6.1 9.3": ["featherweight"], "12.2 12.8 5.7": ["cynics"], "19.7 20.6 26.6": ["troll"], "1.5 11.1 -5.1": ["recharging"], "4.2 20.8 7.2": ["questioner"], "6.4 0.1 1.4": ["widths"], "7.6 13.1 40.4": ["eggplant"], "8.2 10.3 12.6": ["poodle"], "7.8 6.6 20.1": ["riverbank"], "11.1 4.4 3.9": ["heightening"], "2.0 3.8 19.5": ["bauxite"], "23.1 -1.2 3.5": ["freestanding"], "-1.5 15.7 15.5": ["snows"], "12.4 0.4 26.0": ["fishy"], "12.4 16.8 3.3": ["incessantly"], "5.2 12.9 2.6": ["immaterial"], "2.5 0.5 13.9": ["geriatric"], "0.1 -2.4 -4.5": ["sainthood"], "1.5 12.1 13.2": ["cyanide"], "16.1 2.7 23.0": ["sunflower"], "0.9 6.3 6.1": ["omit"], "8.2 -4.1 7.3": ["ruffled"], "7.0 0.4 0.7": ["reclassification"], "1.8 17.7 5.1": ["mopping"], "-9.0 12.2 4.5": ["lyricist"], "3.0 2.6 3.5": ["retraction"], "-10.1 8.5 -5.7": ["meritorious"], "18.0 2.9 16.6": ["sickly"], "14.9 0.3 2.4": ["reams"], "4.3 1.6 9.3": ["backdated"], "7.3 29.3 18.5": ["navies"], "7.8 8.4 4.5": ["dubbing"], "5.6 7.2 4.5": ["hemorrhaging"], "2.6 2.0 0.4": ["foresaw"], "1.5 6.2 7.3": ["accumulates"], "11.6 6.8 8.9": ["hurray"], "13.6 14.0 10.2": ["bewildering"], "2.3 -1.0 6.5": ["reined"], "5.0 -0.6 12.7": ["takings"], "5.1 6.8 6.6": ["soles"], "10.1 14.3 9.3": ["warts"], "7.8 9.1 11.8": ["unsteady"], "4.8 10.4 6.6": ["bookseller"], "5.7 12.7 9.6": ["muddle", "shiftable"], "14.0 3.6 14.2": ["buoyancy"], "10.0 8.5 6.1": ["rattles"], "4.6 5.6 4.8": ["regains"], "2.8 -1.1 0.8": ["amicably"], "20.5 11.6 7.0": ["cuddly"], "16.1 14.3 6.1": ["swaths"], "-1.2 -0.5 5.9": ["shortchanged"], "-2.3 2.0 3.0": ["circumspect"], "7.5 13.1 12.8": ["marooned"], "6.2 3.0 6.0": ["relaxes"], "6.8 5.3 7.1": ["nanoscale"], "10.1 5.5 8.3": ["coils"], "14.2 1.8 -0.3": ["underpins"], "7.9 10.7 12.5": ["bookmaker"], "-3.8 8.7 -4.4": ["strived"], "18.6 2.6 3.6": ["digesting"], "-1.9 5.2 7.6": ["biomarker"], "12.7 10.0 8.5": ["deceptively"], "11.4 6.0 -0.6": ["visionaries"], "4.3 19.8 5.3": ["seduce"], "-6.9 10.5 1.1": ["landlines"], "15.5 14.8 1.7": ["soundly"], "8.0 14.5 10.0": ["grins"], "-1.9 2.8 16.2": ["polysilicon"], "2.6 1.1 22.8": ["bagels"], "13.3 6.3 5.2": ["gazed"], "15.9 15.5 -4.0": ["commandeered"], "5.6 5.3 9.3": ["frontage"], "15.1 2.8 7.0": ["oozing"], "21.7 2.3 0.2": ["multimillionaire"], "14.0 9.9 7.2": ["geometric"], "12.1 7.8 24.2": ["luscious"], "15.2 6.7 12.8": ["figurines"], "3.8 11.8 6.8": ["fraternal"], "10.3 2.8 5.7": ["panache"], "-2.7 12.3 11.2": ["deplete"], "14.2 14.3 5.4": ["thump"], "-3.7 11.3 3.8": ["interviewers"], "6.5 13.4 11.4": ["drapes"], "5.4 11.1 3.3": ["touchy"], "7.5 8.9 5.0": ["manifold"], "-5.9 1.9 3.4": ["psychotherapy"], "0.3 9.0 8.3": ["finality"], "-8.7 7.2 3.9": ["headscarf"], "1.8 19.4 9.3": ["outcast"], "14.0 -0.9 4.9": ["fining"], "-0.6 3.5 7.9": ["scuffled"], "11.2 9.7 0.3": ["tactile"], "12.2 15.2 1.9": ["trampling"], "4.4 14.5 5.6": ["hallucinations"], "5.1 6.9 12.3": ["urn"], "-4.1 3.9 4.8": ["noncommittal"], "-1.0 8.0 2.3": ["bestow"], "8.0 17.6 2.3": ["inert"], "0.9 16.7 5.1": ["subtext"], "-1.5 12.7 7.7": ["replenished"], "3.2 22.5 4.9": ["anathema"], "5.8 2.2 4.9": ["cleantech"], "7.8 7.9 2.6": ["volts"], "-3.5 2.5 8.6": ["reevaluate"], "13.8 7.6 10.9": ["ballerina"], "18.0 0.8 7.1": ["overshadowing"], "8.3 2.4 3.5": ["unenforceable"], "8.6 -1.9 7.5": ["forgoing", "usic"], "0.3 17.8 3.0": ["jailers"], "1.5 10.4 13.2": ["exasperation"], "-3.6 -1.2 12.1": ["heparin"], "5.0 20.9 10.0": ["pawns"], "21.5 11.1 8.6": ["purveyor"], "6.7 18.2 10.9": ["downwind"], "2.9 18.4 4.6": ["allergens"], "7.7 9.6 6.5": ["permeates"], "3.4 4.5 5.8": ["membranes"], "5.7 18.4 4.5": ["hijackings"], "6.1 6.2 12.2": ["backdating"], "10.1 9.1 11.5": ["bumpers"], "8.0 3.3 2.5": ["squeaked"], "-0.2 18.4 4.4": ["radicalism"], "6.5 9.1 3.9": ["rejoicing"], "12.1 6.0 10.2": ["floodlights"], "1.9 -1.1 4.7": ["maxed"], "8.7 9.9 11.6": ["absurdly"], "1.1 11.5 6.7": ["nay"], "0.7 -5.9 -3.7": ["discontinuation"], "-12.5 24.1 1.7": ["martyred"], "15.2 12.3 6.3": ["silo"], "7.3 8.6 8.5": ["meta"], "14.2 9.1 6.7": ["hypnotic"], "0.6 12.1 9.1": ["coexistence"], "5.7 36.0 11.1": ["henchmen"], "1.9 13.3 5.6": ["depreciated"], "14.2 10.6 6.2": ["gasped"], "-3.3 7.9 10.9": ["secondhand"], "-5.2 12.9 2.2": ["disagreeing"], "3.1 5.8 0.4": ["veering"], "0.0 5.7 0.6": ["sedated"], "17.9 13.9 10.5": ["celestial"], "-2.3 15.1 5.2": ["intensification"], "6.4 7.9 5.4": ["indelible"], "6.4 2.2 5.8": ["electricians"], "5.5 22.5 10.4": ["foolishly"], "8.4 5.8 18.0": ["waitresses"], "5.5 -0.5 6.9": ["encapsulated"], "4.8 16.2 8.0": ["actuality"], "3.8 9.0 6.6": ["floodwater"], "20.8 3.5 2.8": ["peddle"], "8.0 22.3 5.9": ["lunatic"], "-8.5 7.5 3.1": ["bunted"], "5.2 25.5 9.5": ["reflexes"], "11.0 8.7 1.6": ["precipice"], "-1.3 2.8 7.9": ["sufficiency"], "6.7 7.5 5.7": ["ringtone"], "-0.5 3.8 -0.9": ["freshen"], "6.1 24.5 6.6": ["detonation"], "11.2 0.8 7.6": ["upend"], "14.3 1.2 6.1": ["curvy"], "18.1 16.9 7.6": ["sandbox"], "6.0 4.6 7.3": ["fortuitous"], "-1.0 0.2 0.5": ["physiotherapy"], "3.2 4.9 3.4": ["emulated"], "22.3 6.6 26.6": ["bountiful"], "7.1 9.5 0.5": ["obscenities"], "11.9 9.5 15.8": ["dunking"], "3.3 1.8 5.4": ["sanguine"], "-6.0 5.4 2.5": ["heptathlon"], "4.9 15.5 -1.2": ["nationalistic"], "-2.1 -1.7 0.7": ["reminisced"], "13.7 12.4 8.2": ["google"], "-1.1 5.3 -2.5": ["sequestered"], "-7.0 -2.8 7.0": ["pp"], "6.3 16.8 3.8": ["claustrophobic"], "1.7 5.2 9.2": ["wettest"], "1.5 12.8 3.5": ["watchful"], "4.4 17.9 19.4": ["shrub"], "18.9 13.3 6.5": ["thundering"], "4.0 -0.2 0.1": ["bandied"], "6.4 3.4 15.4": ["goatee"], "6.2 8.1 6.6": ["kinder"], "6.3 7.9 1.7": ["lastly"], "11.3 18.4 4.0": ["paralyze"], "6.5 -4.8 3.8": ["snowballed"], "5.4 15.0 3.4": ["extricate"], "12.2 20.3 17.5": ["hounds"], "-0.8 29.8 6.6": ["peacetime"], "-3.7 11.1 4.9": ["uncensored"], "2.8 7.2 14.7": ["slapstick"], "-2.6 13.7 -4.6": ["radicalized"], "-3.3 3.1 2.7": ["conserved"], "8.1 6.9 7.0": ["tween"], "4.8 28.7 -1.0": ["unpatriotic"], "10.4 18.5 21.8": ["eater"], "14.0 32.6 5.1": ["diabolical"], "25.0 14.4 9.4": ["engulf"], "7.6 4.2 7.2": ["aghast"], "12.3 6.1 4.1": ["deflate"], "10.2 8.6 12.3": ["elbowing"], "2.4 18.6 11.0": ["indecisive"], "8.1 4.9 9.8": ["processions"], "-8.6 7.7 14.2": ["winemaking"], "13.2 2.8 13.1": ["ensnared"], "10.9 0.4 5.1": ["ramshackle"], "-2.3 22.5 4.6": ["redeploy"], "6.1 -1.1 4.4": ["constipation"], "8.1 16.7 2.8": ["infamy"], "-6.2 4.8 8.3": ["emigration"], "-1.2 11.9 29.3": ["skippers"], "-1.9 2.0 0.9": ["q"], "12.4 12.4 17.3": ["grinder"], "-2.7 16.9 6.8": ["bodily"], "5.3 16.2 12.5": ["bedbugs"], "-1.0 38.7 9.0": ["cowardice"], "3.4 10.3 2.2": ["classifying"], "-0.9 5.2 -1.1": ["nee"], "7.2 16.9 8.2": ["affections"], "7.4 17.9 8.1": ["impossibility"], "12.1 9.6 4.6": ["primacy"], "11.3 2.0 -3.1": ["overhauls"], "0.6 6.8 7.5": ["squabbles"], "6.9 2.7 4.5": ["craved"], "22.7 0.1 2.7": ["inc"], "14.9 23.6 5.7": ["crosshairs"], "13.6 15.6 5.0": ["flicker"], "3.4 12.7 0.9": ["foundational"], "3.2 -1.8 2.8": ["contactless"], "10.9 2.1 8.8": ["overtones"], "6.0 18.4 4.9": ["inoperable"], "-0.1 6.7 10.1": ["stopgap"], "6.6 5.9 5.6": ["disappoints"], "12.5 3.0 12.8": ["woodworking"], "-9.1 3.6 -3.0": ["pulmonary"], "-0.4 6.9 4.9": ["designates"], "11.4 6.6 -3.1": ["managements"], "18.8 5.0 1.2": ["demerger"], "2.0 23.1 5.2": ["undermanned"], "-0.6 1.3 19.1": ["stucco"], "7.5 3.8 14.9": ["fruity"], "10.8 0.7 11.5": ["trolleys"], "-3.7 2.8 9.6": ["leggings"], "-5.1 5.5 -2.4": ["eyewear"], "-1.3 16.7 10.4": ["patrolman"], "9.3 14.5 12.9": ["manhood"], "-2.5 22.5 7.7": ["evasion"], "-2.9 3.9 5.1": ["remixes"], "12.8 23.0 6.4": ["crouched"], "5.1 -0.7 7.6": ["reintroduction"], "-4.9 -4.6 7.8": ["slacks"], "-2.9 2.7 11.9": ["substrates"], "14.7 11.2 6.1": ["peeking"], "-6.8 5.4 5.1": ["acetaminophen"], "-3.1 -4.5 8.4": ["abstracts"], "9.3 6.8 14.0": ["quirk"], "4.3 6.6 12.0": ["butchered"], "2.6 4.5 7.2": ["flabbergasted"], "7.5 28.7 5.2": ["projectiles"], "14.6 1.0 -4.5": ["redesigning"], "4.7 14.5 6.5": ["transcendent"], "14.5 7.6 9.3": ["shroud"], "5.7 16.3 3.5": ["emitters"], "-0.8 6.3 2.5": ["alloys"], "0.8 0.2 -0.8": ["cycled"], "9.4 8.3 12.0": ["facades"], "6.1 7.8 6.2": ["litigants"], "23.2 7.5 10.2": ["rickety"], "5.4 16.3 -4.6": ["saluting"], "7.3 7.9 12.0": ["pane"], "22.7 10.9 1.3": ["bowels"], "1.7 1.7 10.5": ["birthing"], "12.5 8.8 3.6": ["bedeviled"], "-1.9 11.2 13.5": ["tributary"], "-2.7 5.9 5.6": ["jurist"], "16.4 11.0 5.1": ["profiteering"], "1.5 2.6 4.9": ["patronize"], "3.8 11.0 8.2": ["savored"], "7.1 6.1 37.2": ["zucchini"], "15.6 18.1 26.6": ["moths"], "8.4 14.2 5.6": ["weakly"], "5.6 9.1 9.2": ["sweetly"], "2.3 6.5 7.8": ["skydiving"], "18.5 11.2 19.4": ["cactus", "staffie"], "-0.6 7.7 2.3": ["scorecards"], "10.3 2.1 14.2": ["tucking"], "9.1 0.1 8.8": ["pageantry"], "2.0 6.6 11.5": ["matchmaking"], "-0.4 12.4 -0.3": ["degrades"], "8.9 9.1 3.5": ["honking"], "18.0 9.4 7.0": ["forlorn"], "1.5 10.0 2.0": ["reliving"], "-1.3 7.2 6.7": ["tabulated"], "17.1 14.9 10.4": ["hurl"], "5.9 5.0 20.9": ["steakhouse"], "-3.3 1.4 3.9": ["rainout"], "6.3 11.3 5.6": ["purging"], "5.0 10.6 2.3": ["supremely"], "3.9 4.8 9.1": ["gait"], "-0.9 -1.7 0.1": ["biogas"], "9.8 15.2 -2.4": ["thundered"], "3.3 -2.2 6.8": ["kart"], "3.9 20.2 9.0": ["spotter"], "3.3 7.6 7.2": ["alt"], "12.6 2.9 -1.2": ["pasting"], "-1.0 31.2 6.6": ["insurrection"], "11.4 7.6 7.0": ["semantic"], "-4.7 11.8 5.5": ["rushers"], "1.3 1.6 10.2": ["stumping"], "4.9 16.8 17.5": ["poppies"], "2.1 1.9 4.1": ["paralegal"], "-4.9 11.3 1.9": ["radon"], "-8.7 12.4 10.8": ["irrigated"], "1.8 10.2 3.2": ["temporal"], "-6.3 7.2 5.4": ["recitation"], "8.5 9.7 6.9": ["befuddled"], "8.4 32.4 4.4": ["cavalry"], "11.0 10.8 0.2": ["speedily"], "6.8 5.3 5.2": ["amped"], "18.2 8.4 9.2": ["jukebox"], "9.4 9.3 8.4": ["explorations"], "17.7 16.8 3.6": ["lurk"], "2.6 8.4 17.8": ["racehorse"], "6.7 5.7 12.0": ["animators"], "-7.1 9.1 5.2": ["ineffectiveness"], "4.3 3.8 1.5": ["boyish"], "9.9 1.4 0.7": ["audiovisual"], "11.0 13.2 15.9": ["drillers"], "6.2 16.3 2.7": ["arsonist"], "-1.1 16.3 2.9": ["regrettably"], "7.0 5.2 9.2": ["lubricant"], "2.6 9.8 5.9": ["undercurrent"], "4.7 6.0 30.1": ["salted"], "13.0 3.5 10.4": ["gothic"], "-9.9 4.7 3.5": ["tolerability"], "9.3 10.8 -1.0": ["staunchly"], "20.2 7.7 10.6": ["dandy"], "11.6 14.6 4.1": ["angular"], "12.1 1.0 2.7": ["threefold"], "2.5 7.7 -1.3": ["hush"], "-2.1 18.3 12.8": ["resentful"], "1.0 10.1 3.2": ["jurisprudence"], "1.0 9.3 4.5": ["roundabouts"], "4.8 7.1 5.4": ["chatty"], "16.9 -2.2 8.3": ["wrappers"], "22.0 4.1 -2.5": ["trumpeting"], "3.6 6.8 8.5": ["antifreeze"], "3.3 15.7 1.1": ["bugging"], "7.2 0.1 -5.5": ["lauds"], "12.3 9.5 5.2": ["overheat"], "-3.9 -0.2 14.8": ["motherboards"], "-2.6 12.3 0.8": ["untrained"], "6.8 0.8 1.8": ["entrust"], "9.6 2.4 9.9": ["straws"], "4.8 7.5 6.6": ["angers"], "6.0 3.3 20.5": ["migrations"], "14.0 9.8 3.6": ["overseer"], "-1.9 0.1 9.3": ["unsatisfied"], "-9.3 17.4 7.3": ["situational"], "8.9 15.4 2.2": ["solemnly"], "13.1 11.5 6.0": ["contaminating"], "19.4 9.2 36.7": ["moss"], "4.5 3.4 7.3": ["sojourn"], "11.7 7.6 9.0": ["mugging"], "7.0 13.1 3.6": ["shamelessly"], "15.3 5.3 -1.6": ["advancers"], "23.1 5.2 4.2": ["likening"], "10.7 12.7 3.3": ["equations"], "8.7 5.6 5.1": ["clings"], "10.3 23.5 15.3": ["primal"], "-1.6 10.5 10.8": ["headstones"], "9.5 7.2 2.6": ["comatose"], "2.1 7.7 6.7": ["accumulations"], "8.1 1.5 12.3": ["handicrafts"], "12.6 8.6 7.8": ["pee"], "3.5 9.0 2.3": ["flaunt"], "24.3 20.3 15.8": ["devour"], "10.7 0.8 47.3": ["sardines"], "-2.4 7.2 13.5": ["sicker"], "8.5 9.8 12.1": ["discarding"], "7.4 13.3 11.2": ["southward"], "-4.4 24.3 2.9": ["adversarial"], "6.7 5.1 14.8": ["tummy"], "3.5 -1.3 5.6": ["allot"], "1.3 22.8 7.7": ["marksman"], "8.9 13.6 7.2": ["doorways"], "0.7 -2.2 4.3": ["offsite"], "4.7 10.3 18.2": ["nourishment"], "9.3 10.2 2.6": ["thier"], "7.5 4.1 10.0": ["digress"], "5.8 10.5 4.0": ["inhale"], "4.4 1.2 11.6": ["nonunion"], "5.5 29.5 4.7": ["disinformation"], "-6.5 0.9 -2.0": ["dissented"], "-7.3 7.3 9.6": ["curfews"], "-3.0 9.8 12.9": ["renter"], "-1.9 6.2 -5.2": ["inhalation"], "-13.2 14.0 5.8": ["enlistment"], "8.1 2.0 44.5": ["blueberry"], "-1.5 5.6 4.8": ["unstructured"], "10.4 1.5 3.7": ["misspelled"], "10.1 1.4 -1.0": ["accountancy"], "-3.7 17.8 3.2": ["heckling"], "2.0 11.5 7.0": ["unattainable", "moshav"], "8.0 -5.2 1.8": ["vied"], "-0.5 9.4 11.2": ["resettle"], "13.4 15.7 6.2": ["headwind"], "7.9 8.5 11.6": ["pinstripes"], "25.3 1.9 26.4": ["python"], "2.7 15.3 3.9": ["giver"], "5.4 10.2 5.1": ["pronunciation"], "6.7 7.4 12.6": ["nugget"], "-7.8 8.6 6.0": ["uncalled"], "3.3 4.7 9.7": ["streetscape"], "4.6 13.5 8.7": ["quip"], "11.0 9.8 3.5": ["heartthrob"], "7.8 7.1 10.2": ["laborious", "microfilter"], "0.5 10.9 3.4": ["ricin"], "-5.1 6.8 0.2": ["civics"], "11.2 7.4 2.2": ["trouncing"], "4.3 5.8 7.8": ["bunched"], "12.7 1.9 0.6": ["cramming"], "-3.1 4.9 9.9": ["kennels"], "4.4 -2.1 8.2": ["smoothed"], "-3.4 7.9 4.6": ["decomposition"], "5.2 3.7 11.6": ["canvases"], "8.6 7.2 5.5": ["typewriter"], "19.8 14.0 3.9": ["torches"], "4.1 6.6 11.0": ["kilter"], "-3.4 3.0 -0.1": ["solvents"], "8.6 22.7 10.8": ["impotent"], "14.7 6.1 8.4": ["dingy"], "10.3 2.0 8.8": ["scoff"], "1.6 5.9 6.6": ["telepresence"], "-3.2 13.3 1.6": ["disrespected"], "5.6 1.4 8.7": ["drugstores"], "-6.3 19.3 11.4": ["italics"], "5.1 6.5 7.6": ["excavating"], "8.3 13.7 9.7": ["crutch"], "-0.9 4.8 5.9": ["prototyping"], "-0.8 7.6 7.6": ["intergovernmental"], "7.4 3.6 4.8": ["invigorate"], "7.6 6.9 8.4": ["gamely"], "7.4 13.5 11.6": ["pilgrim"], "6.4 14.6 4.2": ["unrestrained"], "-4.2 11.1 9.1": ["holdover"], "-0.0 9.4 9.8": ["muses"], "10.3 15.2 7.4": ["slouch"], "12.8 7.0 13.2": ["tapestry"], "9.8 8.2 16.9": ["capricious"], "10.8 2.0 14.9": ["saucy"], "0.8 18.7 9.2": ["positional"], "2.7 7.6 4.8": ["shadowing"], "7.2 -3.3 5.1": ["megabytes"], "3.1 5.6 27.8": ["raisins"], "16.9 13.4 8.4": ["dominoes"], "17.7 0.2 17.6": ["sparkly"], "0.2 5.4 -5.3": ["previewing"], "14.2 3.6 6.4": ["richly"], "-0.2 16.2 10.7": ["adjective"], "10.8 -3.1 1.4": ["subsidizes"], "10.1 -0.0 7.3": ["dirhams"], "-2.7 6.8 3.6": ["centerfielder"], "20.2 -7.6 1.4": ["fivefold"], "13.1 6.0 15.1": ["chandelier"], "7.9 8.7 17.4": ["sleds"], "13.1 1.2 11.0": ["tugged"], "7.8 14.6 9.7": ["craves"], "1.8 34.6 12.8": ["armaments"], "9.1 -1.4 33.9": ["dumplings"], "3.2 14.3 1.5": ["xenophobic"], "17.6 -3.7 7.0": ["janitors"], "2.5 5.4 5.5": ["sipped"], "11.5 8.0 4.7": ["jamboree"], "-0.2 12.3 11.0": ["lesion"], "-1.9 3.0 0.6": ["radiologists"], "8.6 6.1 18.9": ["jug"], "9.7 2.3 0.2": ["lavishly"], "18.2 -0.5 11.3": ["jumble"], "10.6 0.2 15.5": ["mac"], "20.1 9.0 7.6": ["busily"], "9.5 5.0 31.4": ["veggie"], "10.8 6.3 1.6": ["galloped"], "-2.0 16.3 5.9": ["filibusters"], "8.1 11.9 19.0": ["kites"], "1.2 9.5 1.3": ["emancipation"], "-3.9 2.5 0.3": ["transfusion"], "-6.6 2.1 -5.8": ["runtime"], "-0.7 9.5 8.4": ["choruses"], "4.3 -2.3 2.1": ["securitized"], "17.5 9.1 14.8": ["freaky"], "-1.7 4.4 4.6": ["intermodal"], "14.8 7.4 12.8": ["oddity"], "14.6 8.1 7.8": ["daft"], "7.6 12.2 1.9": ["hundredth"], "13.4 3.2 24.7": ["raspberry"], "2.5 6.8 -3.4": ["disbanding"], "-4.7 7.2 3.7": ["aggravation"], "11.3 13.3 13.3": ["uninvited"], "10.9 13.7 12.8": ["tanking"], "9.9 -0.9 2.8": ["clamps"], "3.2 5.8 5.4": ["modernist"], "9.0 4.8 -1.4": ["depository"], "0.6 3.2 1.0": ["abstentions"], "7.0 11.0 10.2": ["outrageously", "reappearance", "intruded"], "5.5 3.6 10.3": ["uninterested"], "1.6 -0.9 9.6": ["truncated"], "6.8 16.6 11.4": ["redraw"], "5.5 17.5 7.1": ["muttered"], "15.2 10.1 6.1": ["innocently"], "3.7 5.6 1.0": ["outlived"], "-4.5 1.3 19.3": ["nonresidents"], "3.8 12.7 15.9": ["rudder"], "8.1 5.7 1.3": ["originator"], "-4.0 -0.9 6.8": ["unspent"], "1.6 13.9 1.1": ["decontamination"], "10.6 6.6 24.1": ["yummy"], "1.5 3.0 12.3": ["wetter"], "7.1 -3.3 -0.6": ["recycles"], "21.5 2.7 5.9": ["billowing"], "-2.3 4.3 7.2": ["acutely"], "-4.8 4.3 14.5": ["urea"], "-9.9 10.3 5.9": ["dovish"], "4.1 11.1 -1.3": ["publicists"], "8.0 20.6 7.6": ["flees"], "-2.4 1.9 6.4": ["stimulants"], "7.1 14.7 13.8": ["jibe"], "7.9 6.2 11.7": ["mismatched"], "3.0 6.8 27.1": ["brine"], "9.0 1.6 5.6": ["accentuated"], "7.6 9.3 6.6": ["aromas"], "4.1 7.5 15.1": ["hoodie"], "1.5 -1.8 2.1": ["formatted"], "13.6 8.4 21.4": ["bellies"], "13.5 10.1 15.5": ["grinds"], "8.4 3.5 4.8": ["fondling"], "6.8 1.5 6.4": ["technicalities"], "4.0 -0.5 9.8": ["halal"], "4.4 9.5 15.1": ["bbl"], "3.6 -0.9 10.2": ["provenance"], "-0.9 4.5 8.6": ["coed"], "4.3 0.9 4.6": ["serenaded"], "2.3 8.4 5.7": ["portrayals"], "7.3 5.1 5.8": ["vexed"], "2.2 6.0 0.8": ["reunites"], "16.5 21.1 5.9": ["unleashes"], "1.7 12.1 3.5": ["unacceptably"], "17.4 2.8 13.5": ["rakes"], "-4.2 12.6 0.5": ["redeployed"], "2.1 27.0 3.2": ["retaliating"], "2.4 16.1 3.9": ["heroines"], "4.4 4.0 8.3": ["shire"], "4.1 4.8 22.1": ["cookout"], "0.3 3.8 2.1": ["arbitrators"], "14.6 12.8 36.2": ["gator"], "11.7 7.8 14.9": ["uninitiated"], "15.4 9.3 12.6": ["granny"], "10.6 8.6 21.0": ["knuckle"], "-4.2 10.8 1.7": ["coherence"], "9.1 12.3 12.1": ["fable"], "0.9 2.1 9.8": ["indulgent"], "11.6 12.0 21.9": ["amphibians"], "3.2 7.2 5.3": ["homesick"], "4.1 11.8 7.3": ["laziness"], "5.4 2.2 9.7": ["gypsy"], "6.3 7.0 11.5": ["dikes"], "15.8 4.0 6.2": ["rivaled"], "4.3 -2.4 -0.6": ["periodicals"], "5.3 -3.4 10.3": ["juggled"], "7.5 12.2 3.3": ["undaunted"], "7.6 12.2 5.6": ["altruistic"], "14.0 8.7 20.4": ["crusty"], "9.0 4.8 -3.7": ["discriminates"], "6.6 -6.6 10.9": ["dos"], "-4.3 13.8 4.2": ["equalizing"], "11.9 3.3 0.4": ["unconnected"], "-5.5 3.4 6.1": ["unedited"], "2.3 18.5 1.1": ["intuitively"], "12.2 7.2 7.3": ["slanted"], "19.5 4.3 5.2": ["darlings"], "3.2 10.2 5.6": ["accentuate"], "7.0 -1.0 -3.8": ["deluged"], "12.4 13.4 14.5": ["schoolyard"], "2.3 3.8 -1.5": ["prouder"], "-2.0 11.3 2.7": ["photojournalist"], "9.4 6.2 4.0": ["blanking"], "12.7 -6.3 11.9": ["foundered"], "5.8 4.4 18.0": ["farmworkers"], "5.6 5.3 5.1": ["multiplexes"], "1.0 0.9 3.3": ["authorizations"], "13.8 -0.0 18.9": ["pastel"], "5.2 -0.8 -3.9": ["arranger"], "-1.8 8.1 9.0": ["fracking"], "1.6 12.0 3.3": ["scribes"], "-8.2 -2.2 5.7": ["retest"], "-12.6 1.8 0.1": ["signees"], "6.1 -0.2 7.3": ["degenerated"], "1.9 15.1 4.2": ["bushfires"], "-1.3 8.7 10.2": ["adjectives"], "-10.8 -2.9 5.4": ["webinars"], "10.6 31.6 10.2": ["vengeful"], "7.0 7.5 7.3": ["gentler"], "-5.9 4.5 8.0": ["cappella"], "12.9 11.0 12.3": ["rusted"], "3.5 9.2 11.3": ["sores"], "11.3 26.1 11.2": ["goons"], "18.1 12.1 14.2": ["deformed"], "-2.4 0.5 -3.2": ["collaborates"], "-5.9 18.9 8.0": ["returner"], "17.3 10.1 11.5": ["gouging"], "18.2 34.8 16.2": ["undead"], "6.5 3.7 14.3": ["incense"], "8.1 7.9 4.4": ["mathematician"], "5.2 3.3 13.2": ["expat"], "-1.5 9.7 2.7": ["mediapersons"], "-4.3 4.3 -3.0": ["rezoned"], "-1.0 4.6 -5.6": ["applicability"], "-1.0 0.6 17.3": ["crafters"], "5.8 3.0 1.1": ["uprights"], "0.6 3.8 7.3": ["damper"], "-3.2 6.5 8.3": ["trumpeter"], "-1.7 1.9 1.7": ["radiologist"], "2.6 7.9 4.5": ["suave"], "8.2 8.2 26.8": ["jacks"], "-2.4 7.0 5.6": ["goodbyes"], "14.3 11.8 8.5": ["bulletproof"], "3.5 13.6 11.2": ["gruff"], "3.9 0.0 24.7": ["brownies"], "6.4 -0.6 6.6": ["storeys"], "3.5 5.3 8.2": ["wastage"], "15.2 -2.0 6.8": ["brouhaha"], "-4.6 9.7 4.4": ["frustrates"], "3.8 -1.0 3.6": ["disheveled"], "19.3 8.3 1.5": ["trumpets"], "11.8 6.3 14.7": ["chomping"], "1.7 18.4 10.8": ["virtuous"], "2.2 12.7 -0.5": ["tiredness"], "26.4 9.9 12.5": ["gobble"], "11.4 9.5 9.4": ["pleasantly"], "3.7 8.4 3.4": ["burners"], "2.2 -3.2 -1.0": ["rf"], "2.3 4.7 8.3": ["housework"], "-2.9 6.1 7.5": ["reagents"], "3.0 6.6 9.2": ["rougher"], "1.1 5.1 6.4": ["earful"], "11.2 3.8 2.9": ["resurrecting"], "0.6 20.4 3.4": ["repent"], "5.8 9.2 8.7": ["footers"], "6.8 22.2 8.9": ["kneel"], "15.9 19.8 7.3": ["lurks"], "9.1 16.9 12.1": ["bureaucracies"], "1.2 13.4 2.7": ["emergent"], "5.1 7.8 18.0": ["deliciously"], "4.0 -1.0 17.8": ["restocking"], "11.7 4.1 6.0": ["brandished"], "11.6 5.0 7.7": ["squeak"], "13.0 12.8 8.4": ["figurative"], "9.4 11.9 9.8": ["frown"], "13.7 -3.3 1.9": ["postpones"], "8.6 2.2 8.0": ["rockin"], "1.6 7.2 6.4": ["dyslexia"], "8.0 13.8 7.5": ["embarrassingly"], "8.9 8.5 15.0": ["tinted"], "7.3 12.9 -2.1": ["abduct"], "11.9 9.4 4.9": ["brunette"], "-5.9 -2.3 3.7": ["gynecologist"], "6.0 27.5 10.1": ["endgame"], "-6.1 16.8 13.1": ["wideouts"], "5.7 7.3 12.6": ["porches"], "0.3 1.7 1.2": ["refreshingly"], "0.3 5.8 19.5": ["aromatic"], "4.2 -2.8 7.2": ["nannies"], "17.7 11.1 24.1": ["feathered"], "15.2 21.0 8.3": ["impervious"], "-2.1 -0.4 7.6": ["reissue"], "4.8 10.8 4.6": ["transcended"], "-1.9 36.6 9.0": ["occupier"], "-4.7 20.3 5.1": ["talker"], "-1.9 10.7 8.6": ["foursomes"], "16.4 0.1 14.2": ["powdered"], "-3.2 6.7 12.7": ["crosswalks"], "-9.4 1.4 5.7": ["propofol"], "8.9 7.3 26.8": ["antlers"], "1.8 15.7 1.2": ["prewar"], "0.9 13.6 44.5": ["quail"], "16.4 14.7 22.2": ["hatching"], "3.0 5.4 -1.5": ["redeveloping"], "-0.7 4.2 3.0": ["perfumes"], "1.5 5.0 2.9": ["podiums"], "-11.5 -3.8 13.0": ["weatherization"], "3.8 18.0 7.1": ["insecticides"], "0.6 5.6 3.6": ["perturbed"], "20.3 21.2 17.8": ["elf"], "16.3 6.4 4.4": ["flutter"], "3.9 -2.8 20.6": ["fleshed"], "14.5 16.1 11.8": ["stinking"], "6.7 12.2 6.2": ["imperatives"], "3.7 9.7 6.8": ["rosary"], "-3.1 2.3 4.5": ["amplification"], "-1.8 2.4 0.8": ["underrepresented"], "23.8 18.3 22.0": ["cockroaches"], "0.3 5.7 2.4": ["milieu"], "5.9 17.3 3.9": ["vices"], "-3.1 6.1 5.0": ["cognition"], "-0.8 7.0 8.6": ["ballplayers"], "8.5 12.7 6.7": ["minding"], "3.8 23.2 8.6": ["miscalculation"], "0.4 2.3 13.7": ["flamenco"], "6.3 1.2 10.8": ["fete"], "8.2 18.9 31.0": ["raccoons"], "5.1 1.6 11.3": ["fussy", "trimmer"], "3.3 -2.9 -1.2": ["turnarounds"], "15.9 8.1 9.8": ["splashes"], "0.0 18.2 9.5": ["frostbite"], "-0.9 8.4 4.1": ["illiquid"], "6.2 12.5 17.3": ["bunting"], "7.3 11.7 13.8": ["agro"], "7.1 6.0 16.2": ["pantomime"], "13.3 3.7 14.8": ["sculpting"], "0.7 26.9 -2.2": ["courageously"], "-9.7 -1.4 9.7": ["disbursements"], "-2.0 5.7 11.6": ["culverts"], "12.4 11.1 11.5": ["festering", "sies"], "2.9 10.9 3.7": ["newsrooms"], "4.8 14.2 39.4": ["shorelines"], "5.7 14.6 26.2": ["foraging"], "-5.8 0.6 11.3": ["mandolin"], "3.4 18.3 1.0": ["arsonists"], "-6.0 8.7 5.8": ["screenwriters"], "-0.4 4.8 65.1": ["halibut"], "-6.5 14.8 9.3": ["presumptive"], "-2.5 1.9 -2.9": ["earphones"], "16.1 11.8 4.1": ["rebuff"], "10.9 6.4 12.8": ["shouldering"], "2.0 4.0 11.9": ["vegetative"], "9.6 5.5 4.0": ["craziest"], "0.6 0.7 7.9": ["tenancy"], "5.3 14.1 3.0": ["workforces"], "10.5 21.6 7.3": ["pernicious"], "-12.1 8.8 4.4": ["relapsed"], "-1.2 2.8 4.3": ["correlates"], "3.7 8.0 11.2": ["downer"], "0.5 5.4 27.6": ["garnish"], "14.7 14.9 7.9": ["fantastical"], "-3.4 21.2 4.6": ["unfaithful"], "-8.9 6.3 17.9": ["spayed"], "19.4 7.9 7.8": ["edifice"], "12.6 3.5 7.4": ["squeezes"], "12.4 11.0 3.8": ["dousing"], "3.7 7.8 2.3": ["appreciable"], "-1.6 3.7 7.9": ["infill"], "18.8 8.7 13.7": ["caged"], "-0.1 4.6 12.8": ["tendons"], "2.0 21.0 10.3": ["conversely"], "4.5 5.9 1.1": ["mails"], "3.1 12.1 4.8": ["loosing"], "8.1 13.3 4.2": ["banal"], "3.6 4.1 5.8": ["peptides"], "8.9 3.0 14.8": ["quart"], "3.5 18.2 9.7": ["factly"], "5.7 -1.4 -4.4": ["conned"], "0.2 -0.9 -0.5": ["reconfiguration"], "3.4 10.2 0.2": ["inducement"], "-6.9 10.8 4.6": ["assayed"], "4.4 24.2 6.0": ["extermination"], "6.5 7.3 21.6": ["midsummer"], "9.5 6.3 3.5": ["showman"], "19.5 7.6 13.5": ["princesses"], "13.7 7.8 24.3": ["feasting"], "13.9 18.0 9.7": ["disfigured"], "-5.0 3.4 7.9": ["dressage"], "7.0 14.9 3.3": ["gassed"], "6.3 12.9 7.1": ["juxtaposition"], "20.0 11.2 5.3": ["panorama"], "7.0 5.5 3.8": ["compensates"], "9.8 6.2 11.5": ["meteorite"], "11.4 5.8 12.9": ["coaxing"], "6.4 9.1 18.0": ["moored"], "-0.2 1.7 0.4": ["corresponded"], "9.5 8.9 15.8": ["droppings"], "3.1 -1.5 9.3": ["med"], "-10.6 -3.3 0.3": ["mentorship"], "-2.0 12.0 11.6": ["headstone"], "4.1 12.7 9.5": ["remakes"], "-2.0 22.2 9.7": ["tactician"], "7.0 10.5 12.0": ["mercifully"], "1.7 3.9 11.1": ["wistful"], "5.8 12.9 15.3": ["clothesline"], "5.2 14.0 15.7": ["seaports"], "11.9 4.6 -1.4": ["expandable"], "3.2 -0.3 9.9": ["jazzy"], "2.9 4.5 10.3": ["basilica"], "8.7 13.4 7.8": ["traversing"], "-8.7 8.0 12.7": ["prioritization"], "5.9 2.3 1.2": ["centrifuge"], "0.7 12.6 2.4": ["secede"], "10.5 3.9 3.0": ["bolting"], "28.3 3.1 21.5": ["glistening"], "7.7 9.1 0.6": ["couriers"], "9.7 8.9 3.8": ["dials"], "6.8 -2.3 17.4": ["caterers"], "25.3 4.7 -1.1": ["rivaling"], "3.5 7.3 15.7": ["progeny"], "-0.8 25.9 5.7": ["fallacy"], "9.1 15.9 5.2": ["unionists"], "16.3 2.6 1.6": ["reverberated"], "4.8 21.7 10.0": ["cheaters"], "18.8 11.7 3.6": ["zipping"], "-0.3 6.7 3.6": ["politicize"], "2.1 11.4 17.7": ["butchers"], "7.9 10.8 -3.4": ["snooping"], "-1.7 9.1 1.4": ["precludes"], "9.0 5.9 16.0": ["sugary"], "19.3 19.5 32.2": ["moth"], "11.5 3.5 15.9": ["caterer"], "3.9 0.2 0.7": ["groped"], "22.6 -1.0 4.0": ["heralding"], "3.1 6.4 17.0": ["prefecture"], "-5.6 0.6 36.9": ["venison"], "6.6 4.6 11.5": ["poolside"], "2.3 -1.9 12.4": ["binder"], "14.1 7.0 1.5": ["conspicuously"], "6.2 0.4 2.7": ["redone"], "4.8 -0.6 -1.2": ["cofounder"], "-1.4 4.4 13.4": ["gluten"], "7.0 4.6 2.6": ["vigils"], "0.4 -2.2 13.3": ["micron"], "9.4 9.9 11.5": ["squatting"], "25.8 10.5 4.7": ["flickering"], "7.8 3.3 36.9": ["pear"], "7.1 8.6 7.6": ["undamaged"], "12.3 6.9 7.8": ["slung"], "10.0 21.3 2.0": ["kidnapper"], "6.0 9.3 7.1": ["treading"], "25.0 15.0 22.8": ["bunnies"], "6.9 2.3 8.6": ["copped"], "13.3 14.4 9.0": ["entryway"], "10.1 14.6 9.0": ["intransigence"], "15.7 10.8 9.3": ["cloaked"], "5.1 4.3 -3.6": ["restructurings"], "-0.1 9.5 -5.2": ["retook"], "-10.1 -0.1 1.7": ["reappointment"], "-5.8 -2.6 0.1": ["reissued"], "-3.6 10.2 -2.8": ["utterances"], "1.2 6.0 8.4": ["affluence"], "11.7 3.8 5.4": ["escalators"], "-3.2 8.0 2.6": ["influencers"], "7.6 21.8 1.4": ["controllable"], "8.2 13.5 11.6": ["undefined"], "10.3 -1.1 -3.2": ["discontinuing"], "-3.7 -0.3 -6.4": ["familiarize"], "5.3 6.6 6.8": ["meddle"], "9.1 0.9 2.9": ["speedier"], "7.6 6.7 4.0": ["morbid"], "8.5 7.4 3.5": ["buttress"], "-1.0 10.5 7.7": ["inbounds"], "1.6 0.3 2.0": ["cardiologists"], "-0.3 5.4 -1.9": ["furthers"], "-0.8 0.3 6.3": ["lofts"], "3.9 5.9 3.3": ["classifies"], "5.0 11.7 0.4": ["tipster"], "13.2 8.9 10.2": ["scarlet"], "4.1 3.2 8.5": ["proprietors"], "-2.8 -1.1 -5.8": ["availed"], "10.3 11.6 12.4": ["bums"], "13.7 12.0 8.6": ["demented"], "9.3 11.6 9.6": ["shear"], "8.9 15.4 11.6": ["housemate"], "-4.4 18.9 4.9": ["intifada"], "7.7 14.3 5.2": ["bothersome"], "2.3 10.5 5.0": ["narrowest"], "13.7 21.8 2.3": ["cabal"], "11.9 17.0 6.6": ["crucified"], "3.0 2.0 1.3": ["uncomplicated"], "8.5 3.4 0.9": ["aero"], "18.3 6.8 28.6": ["tortoise"], "13.5 4.6 39.6": ["melon"], "7.2 -1.9 5.2": ["yo"], "10.0 14.6 10.0": ["psycho"], "18.4 9.5 6.7": ["drumbeat", "pandora"], "6.7 11.1 10.1": ["stroking"], "10.7 0.9 4.5": ["ingesting"], "7.0 6.9 13.5": ["throwaway"], "5.3 7.5 11.6": ["parodies"], "-0.5 1.9 11.7": ["sterilized"], "1.1 4.5 14.2": ["wry"], "12.7 11.5 3.6": ["doorsteps"], "14.3 5.2 43.0": ["fin"], "-6.7 0.9 8.0": ["reprint"], "11.6 14.7 4.1": ["disintegrate"], "5.0 20.0 6.1": ["escapees"], "7.5 -2.4 1.5": ["injects"], "-1.3 1.9 11.7": ["distillery"], "27.1 24.1 12.4": ["almighty"], "-2.0 12.5 -0.2": ["impressionable"], "9.3 4.0 11.3": ["quicken"], "-2.7 10.5 16.5": ["replenishment"], "-1.8 14.7 12.7": ["speeders"], "4.8 27.2 10.4": ["affliction"], "5.5 24.0 12.5": ["thy"], "2.2 1.1 2.0": ["synthesized"], "2.1 14.1 15.8": ["coca"], "3.7 16.8 9.1": ["cybercrime"], "11.6 19.4 12.0": ["adventurers"], "1.2 12.7 6.8": ["hierarchical"], "1.4 10.4 8.9": ["flurries"], "6.2 11.3 13.2": ["conservationist"], "-3.7 5.2 0.0": ["armband"], "4.6 6.4 2.8": ["shootaround"], "3.4 8.3 5.3": ["modicum"], "6.5 6.7 15.1": ["statehouse"], "20.0 6.0 1.8": ["flogging"], "1.1 19.6 13.8": ["foolishness"], "0.8 3.1 18.0": ["ovaries"], "5.5 12.0 0.8": ["denounces"], "0.6 5.6 7.7": ["deacon"], "18.0 23.0 2.9": ["phobia"], "18.7 3.2 6.0": ["scented"], "5.0 -1.8 0.4": ["terabytes"], "16.2 5.7 5.9": ["scurried"], "8.5 13.9 8.1": ["wither"], "0.9 0.1 0.7": ["worded"], "5.3 14.1 4.3": ["fanbase"], "7.9 2.7 3.6": ["eschew"], "-1.8 -0.4 41.5": ["veal"], "2.9 -1.2 7.0": ["implantation"], "1.5 1.7 -7.3": ["analyzer"], "9.3 -0.8 0.9": ["bypasses"], "7.9 7.9 17.9": ["knuckles"], "10.6 15.0 32.6": ["cove"], "5.1 9.8 5.8": ["divider"], "7.4 -2.1 -6.6": ["rubbished"], "13.7 20.8 -0.5": ["demonized"], "10.5 4.1 9.7": ["hodgepodge"], "-2.0 4.4 13.4": ["preservatives"], "-2.6 3.7 5.0": ["percussionist"], "15.7 9.9 29.5": ["seafloor"], "8.7 8.3 15.8": ["artful"], "16.4 13.5 20.2": ["cutthroat"], "5.3 13.3 5.8": ["unflappable"], "13.4 15.4 9.2": ["docile"], "-0.6 12.3 5.8": ["intrude"], "12.4 6.3 12.9": ["withered"], "11.6 12.8 0.9": ["indignity"], "4.0 25.1 -1.2": ["hypocrites"], "-3.3 12.4 6.9": ["gratification"], "8.5 20.3 13.4": ["madly"], "10.1 10.0 25.1": ["rhino"], "8.9 0.8 6.8": ["underperformance"], "2.4 22.5 -1.0": ["jailer"], "6.3 21.6 13.2": ["deflationary"], "-6.9 -7.4 6.6": ["terminations"], "-0.5 23.8 -1.7": ["antagonistic"], "-1.1 15.8 2.4": ["repentance"], "-4.5 22.1 6.6": ["opportunist"], "0.5 11.3 -3.1": ["forgave"], "11.8 0.6 13.3": ["swag"], "-5.5 0.1 10.7": ["matinees"], "4.5 16.3 -0.3": ["purify"], "-4.1 -1.1 -0.4": ["reconnected"], "4.1 5.9 0.6": ["gauged"], "-0.6 6.6 3.7": ["respirator"], "-0.8 0.2 8.3": ["retainer"], "-4.7 -2.0 11.8": ["fibromyalgia"], "6.1 23.0 8.2": ["battlegrounds"], "-2.6 9.5 7.4": ["characterizations"], "5.1 -2.6 2.3": ["rewrote"], "1.4 21.4 1.1": ["shortcoming"], "12.4 11.2 1.5": ["uncompetitive"], "-7.0 4.1 7.0": ["athletically"], "5.1 14.6 10.7": ["thou"], "27.8 3.6 18.5": ["giraffe"], "2.2 7.8 7.0": ["motioned"], "1.3 10.9 12.0": ["creationism"], "-0.2 27.0 7.0": ["unforgivable"], "-0.9 18.4 4.2": ["disinfectant"], "4.9 3.6 8.0": ["tardy"], "4.9 14.6 2.7": ["slurs"], "17.7 8.7 8.4": ["suburbia"], "28.3 13.0 14.2": ["gobbling"], "14.2 15.6 6.7": ["muttering"], "12.0 12.5 2.9": ["surreptitiously"], "14.0 32.0 19.0": ["ninja"], "13.8 10.2 22.6": ["frying"], "1.8 11.2 -0.8": ["optimally"], "23.4 9.6 7.0": ["morphing"], "19.9 14.3 5.0": ["morons"], "16.5 -4.0 12.1": ["wrapper"], "1.4 12.3 8.9": ["payloads"], "6.3 4.8 23.6": ["potted"], "0.2 9.5 12.6": ["cartoonists"], "-0.4 3.0 2.1": ["orthopedics"], "7.5 19.1 13.9": ["lunge"], "-0.4 11.9 1.6": ["ions"], "5.3 5.6 10.7": ["cupboards"], "7.1 5.0 16.8": ["sneaker"], "4.4 13.6 11.7": ["twisters"], "-0.6 20.6 7.1": ["sectarianism"], "34.4 3.3 17.9": ["multicolored"], "7.6 1.7 8.8": ["doghouse"], "0.3 5.4 -0.4": ["decathlon"], "12.0 3.2 13.4": ["chandeliers"], "8.5 9.3 8.9": ["industrious"], "3.8 10.7 13.8": ["newbie"], "2.9 1.4 5.7": ["systemwide"], "16.0 22.6 11.5": ["otherworldly"], "9.9 8.7 7.7": ["middling"], "8.9 6.4 7.6": ["confederation"], "9.5 5.1 3.5": ["incarnations"], "5.8 10.0 12.5": ["gregarious", "fatness"], "-6.9 0.8 2.6": ["manageability"], "8.0 17.3 9.1": ["sneaks"], "-0.8 18.5 -0.9": ["repugnant"], "10.8 12.7 2.5": ["enlarging"], "0.5 0.9 10.2": ["coffeehouse"], "-6.6 10.5 -2.8": ["apolitical"], "12.9 -5.5 0.8": ["spotlighted"], "2.3 9.1 49.9": ["fishers"], "8.9 4.3 -1.7": ["prescient"], "-0.8 2.1 -0.3": ["proofs"], "19.3 27.8 17.4": ["knights"], "1.6 10.9 3.4": ["servicer", "berates"], "14.3 7.4 14.0": ["mannequin"], "0.3 3.2 26.1": ["fillings"], "23.6 10.6 21.1": ["snowman"], "8.6 8.2 1.2": ["overestimated"], "4.7 12.4 4.0": ["franchisor"], "-1.3 13.2 1.2": ["counterparty"], "1.2 20.7 4.3": ["concealment"], "1.1 -1.3 9.5": ["apprenticeships"], "-0.3 0.6 4.9": ["cramping"], "6.4 -2.6 3.5": ["conservatorship"], "7.2 6.5 7.9": ["synch"], "11.0 15.4 4.8": ["devotee"], "6.2 13.8 2.5": ["unplayable"], "4.7 2.8 33.4": ["beets"], "6.5 17.3 8.5": ["spores"], "4.6 1.6 -0.2": ["undated"], "0.3 15.2 -3.0": ["unflinching"], "1.6 6.8 6.7": ["proportionately"], "-2.9 1.0 7.1": ["workweek"], "-1.6 1.3 21.6": ["dredged"], "8.0 8.3 12.7": ["bian"], "12.8 23.0 6.1": ["bulwark"], "-8.7 18.7 -1.0": ["commonality"], "-4.3 0.8 8.2": ["roundtrip"], "-0.3 16.4 0.1": ["overconfident"], "5.7 19.2 10.6": ["enforcers"], "13.1 12.7 12.9": ["acrobatics"], "16.2 2.1 8.7": ["glum"], "-1.8 8.2 12.0": ["footnotes"], "12.7 6.2 6.8": ["jettison"], "11.9 4.0 12.2": ["laminated"], "1.3 2.0 7.6": ["compacts"], "5.7 6.6 7.1": ["dreading"], "10.1 -0.5 5.6": ["rotunda"], "0.6 0.1 -0.2": ["placenta"], "1.9 10.1 9.8": ["minimally"], "1.9 12.7 3.4": ["coughs"], "-0.1 8.1 9.9": ["biologic"], "5.6 1.1 2.5": ["ebbed"], "-0.9 2.2 8.6": ["grandfathered"], "18.8 16.3 10.7": ["snarling"], "8.0 34.3 20.6": ["destroyers"], "-3.8 7.5 14.2": ["gratuity"], "-2.0 2.8 5.4": ["expulsions"], "-1.9 7.1 1.1": ["domiciled"], "7.3 4.4 5.0": ["dinars"], "9.8 8.3 3.3": ["pickets"], "10.7 19.7 9.5": ["ugliness"], "11.9 7.0 5.4": ["imprinted"], "6.9 4.6 4.1": ["buzzword"], "-0.6 -2.8 2.1": ["tabling"], "-4.4 24.7 6.6": ["factional"], "-2.5 14.1 7.0": ["calmness"], "-0.8 21.2 12.8": ["feudal"], "13.8 2.4 5.5": ["meltdowns"], "7.5 11.4 10.8": ["nocturnal"], "3.0 10.1 16.0": ["dong"], "-0.5 5.1 -4.2": ["notifies"], "10.1 11.6 10.2": ["stutter"], "5.0 15.4 12.9": ["pagan"], "-7.9 -0.2 8.4": ["repertory"], "-0.4 2.5 12.9": ["viaduct"], "15.1 9.8 7.7": ["yawning"], "6.8 -3.1 7.2": ["balking"], "4.2 12.9 7.8": ["unabashedly"], "0.8 7.6 6.8": ["serotonin"], "8.6 28.9 19.6": ["amphibious"], "3.4 17.9 4.3": ["upfield"], "5.1 8.2 11.2": ["disinvestment"], "13.6 16.0 5.7": ["doomsday"], "14.4 -1.4 4.3": ["offloaded"], "1.4 8.1 6.2": ["storytellers"], "9.7 23.5 2.9": ["detonating"], "0.7 5.8 11.4": ["paucity"], "0.3 13.7 3.1": ["provokes"], "5.6 -1.9 10.4": ["rodeos"], "18.0 13.1 8.0": ["movable"], "-4.9 9.8 4.5": ["disciplining"], "-0.7 8.1 7.5": ["hajj"], "5.1 8.7 13.2": ["sluggers"], "13.4 -7.2 16.8": ["skimpy"], "-2.1 21.5 8.0": ["undisciplined"], "14.2 0.9 6.9": ["techs"], "20.4 16.0 5.6": ["blinked"], "2.8 -3.6 7.2": ["fizzle"], "10.4 5.8 3.3": ["chimes"], "-6.2 2.5 2.8": ["faucets"], "-2.7 34.1 2.6": ["interrogator"], "14.1 5.3 7.1": ["shuttering"], "7.0 11.7 3.3": ["unitary"], "-4.8 2.6 4.5": ["fiscally"], "-2.9 3.9 1.7": ["fractional"], "-3.9 7.0 -2.8": ["conciliation"], "7.1 -0.5 -2.7": ["quelled"], "2.6 -2.1 -0.1": ["renegotiation"], "2.2 -3.2 2.8": ["rejections"], "3.3 7.9 8.7": ["pompous"], "1.2 0.7 7.3": ["gravitas"], "17.8 -3.1 5.6": ["mushrooming"], "-0.3 4.2 7.9": ["overreacted"], "-7.4 14.5 -4.8": ["inadmissible"], "-12.3 9.7 10.2": ["platelets"], "8.0 14.6 3.7": ["monotonous"], "0.5 -1.9 -2.5": ["alumna"], "4.1 2.1 10.4": ["auctioneers"], "6.3 23.5 7.6": ["assuredly"], "-3.0 2.5 13.6": ["cuttings"], "11.3 2.4 10.0": ["livery"], "9.9 18.4 7.0": ["scarier"], "16.7 9.7 15.0": ["moat"], "-0.7 -2.2 1.0": ["gynecology"], "16.1 17.5 26.9": ["skunk"], "3.6 18.6 11.1": ["unafraid"], "9.2 10.6 4.2": ["illuminates"], "0.8 5.8 3.8": ["plebiscite"], "9.4 15.4 7.2": ["overreaching"], "-0.0 4.1 5.8": ["backpackers"], "10.5 28.0 1.2": ["genocidal"], "7.4 15.7 18.7": ["coastguard"], "18.1 16.4 21.3": ["albatross"], "-4.9 8.7 4.7": ["mannerisms"], "7.7 4.3 12.2": ["nonessential"], "4.4 7.4 20.8": ["causeway"], "9.5 6.4 9.6": ["wildcat"], "-4.8 4.7 10.6": ["saline"], "9.9 4.0 13.1": ["stools"], "4.0 0.4 14.9": ["j"], "11.5 12.6 3.5": ["gallows"], "-6.2 9.0 -1.1": ["recuperation"], "3.6 4.7 16.3": ["ethylene"], "2.4 4.2 10.4": ["pendant"], "18.6 11.7 6.4": ["aficionado"], "10.3 11.0 6.4": ["magnificently"], "6.8 14.7 37.1": ["trawler"], "2.7 0.6 13.2": ["uploads"], "5.7 9.6 0.5": ["scolding"], "13.3 8.1 4.3": ["tether"], "4.5 9.0 10.2": ["footpaths"], "9.4 14.5 6.1": ["lockstep"], "5.4 14.5 4.5": ["boldness"], "13.9 5.1 8.2": ["howls"], "15.1 3.4 15.7": ["caper"], "8.0 2.8 9.0": ["infomercial"], "10.4 1.9 8.4": ["omnibus"], "9.4 17.9 -0.1": ["impersonal"], "4.1 0.8 23.3": ["tortillas"], "17.6 2.4 4.5": ["mimicked"], "8.6 25.2 19.2": ["admiral"], "2.1 12.5 1.4": ["repudiation"], "3.5 17.6 -2.9": ["deluded"], "21.3 22.1 12.9": ["metaphorical"], "8.5 4.6 -1.2": ["detonators"], "18.8 -5.6 5.5": ["octuplets"], "10.0 9.1 3.2": ["utilitarian"], "6.9 1.5 7.9": ["gush"], "-1.0 -4.6 9.4": ["registrars"], "-7.1 8.1 33.2": ["walleyes"], "12.7 0.2 10.1": ["perky"], "25.2 2.6 5.7": ["bigwigs"], "12.2 22.0 5.5": ["repulsive"], "7.5 11.7 3.9": ["clergyman"], "-5.8 4.2 0.2": ["inquires"], "12.0 4.8 9.9": ["planetarium"], "-11.0 5.4 1.7": ["airplay"], "20.6 -1.6 12.4": ["gilded"], "-13.2 5.9 4.0": ["imparted"], "6.8 9.5 2.8": ["covet"], "-2.2 8.4 25.2": ["martini"], "-0.8 8.4 20.2": ["brandy"], "5.7 -1.0 10.2": ["bicentennial"], "24.9 -4.2 9.1": ["splashy"], "4.5 9.7 1.5": ["unsurprising"], "8.2 3.7 1.0": ["unplugged"], "-5.7 3.8 10.2": ["statin"], "-3.6 29.3 7.4": ["sorties"], "4.6 8.1 -0.1": ["imbued"], "-5.6 13.7 -4.0": ["misconstrued"], "17.3 14.4 9.0": ["infamously"], "7.8 18.5 -4.5": ["overstretched"], "0.1 17.2 6.9": ["antagonism"], "10.0 3.8 5.6": ["signified"], "7.3 7.3 10.6": ["sitter"], "15.9 2.5 5.5": ["hyperactive"], "4.1 10.7 2.8": ["overused"], "-4.0 2.2 7.3": ["freehold"], "5.1 7.8 1.0": ["electrification"], "-4.1 2.0 3.7": ["timings"], "19.2 7.9 3.6": ["savaged"], "29.3 1.2 5.7": ["festooned"], "9.6 6.8 2.6": ["telemetry"], "16.3 9.5 7.1": ["gouge"], "3.3 14.7 3.4": ["willed"], "2.0 4.7 -1.0": ["caravans"], "8.9 10.6 8.8": ["grime"], "0.7 6.3 2.0": ["outhit"], "-4.3 6.2 5.4": ["holidaying"], "-0.2 -3.1 -0.6": ["verifies"], "2.1 10.7 8.6": ["inadequacy"], "6.1 9.5 11.8": ["abs"], "6.0 21.4 6.3": ["perverted"], "13.9 10.9 3.1": ["hunched"], "-1.1 8.1 4.1": ["duplicating"], "2.3 12.6 3.1": ["engender"], "11.7 15.4 1.8": ["broadside"], "18.2 28.5 14.3": ["mechanized"], "8.6 14.9 7.4": ["carelessly"], "3.9 3.7 2.7": ["relieves"], "7.2 2.6 10.3": ["vaudeville"], "3.0 16.5 1.1": ["iota"], "4.3 21.0 11.3": ["curses"], "2.6 5.7 9.3": ["comps"], "11.3 8.1 6.2": ["temperamental"], "-0.2 6.8 3.9": ["melodramatic"], "4.8 12.3 3.1": ["dis"], "8.6 27.7 6.9": ["tyrannical"], "1.2 10.0 3.0": ["pluses"], "-3.1 4.8 8.4": ["steeplechase"], "33.7 13.5 14.5": ["lumbering"], "-6.0 1.6 11.1": ["impound"], "9.0 10.7 3.1": ["milliseconds"], "13.5 -6.4 -3.1": ["picketed"], "-4.8 6.0 -5.3": ["implicating"], "4.1 8.9 8.7": ["extraneous", "tryng"], "-0.5 0.7 1.9": ["concurrence"], "5.7 7.1 7.4": ["doorman"], "7.2 4.8 8.5": ["elbowed"], "15.4 16.9 5.7": ["cursor"], "17.4 20.4 3.3": ["acquirer"], "9.6 -1.5 10.2": ["pouches"], "-2.0 14.6 9.5": ["jest"], "9.9 8.7 11.7": ["canny"], "14.1 12.5 7.3": ["twinkle"], "-6.9 2.0 3.2": ["reassessed"], "2.3 10.1 8.0": ["glances"], "9.1 14.5 -0.3": ["irrevocable"], "3.1 4.2 5.4": ["listers"], "3.2 9.0 6.5": ["gardai"], "2.7 8.3 -0.3": ["cathartic"], "3.1 0.8 19.1": ["keg"], "15.1 15.6 10.5": ["meek"], "3.8 1.7 0.6": ["boulevards"], "5.9 1.3 2.4": ["resonating"], "2.9 3.3 -2.2": ["interned"], "10.1 17.2 6.4": ["starkly"], "6.5 10.5 4.3": ["delirious"], "7.4 13.8 5.2": ["inadequacies"], "16.8 20.8 8.6": ["launcher"], "8.4 8.1 12.2": ["waistline"], "8.0 5.5 45.4": ["mullet"], "-4.4 12.8 -6.1": ["executor"], "-11.5 10.2 8.9": ["mixtape"], "6.2 2.9 7.5": ["dictionaries"], "-1.4 18.3 0.1": ["allegiances"], "-5.0 13.4 4.4": ["memorized"], "18.7 8.3 8.9": ["glories"], "13.0 4.5 9.8": ["prettier"], "4.9 12.5 4.0": ["unhinged"], "6.4 6.1 12.9": ["rafts"], "1.6 5.1 11.2": ["subtracted"], "1.2 6.3 4.9": ["narrates"], "1.8 6.0 4.2": ["legislated"], "5.8 7.1 13.8": ["snacking"], "0.4 2.5 10.9": ["lam"], "14.6 7.3 5.2": ["meld"], "0.4 13.9 -5.9": ["bugged"], "0.3 11.0 -1.6": ["inconveniences"], "12.6 -2.1 5.9": ["spokes"], "7.7 1.8 15.0": ["napkins"], "17.3 9.8 11.4": ["freakish"], "0.6 13.0 3.0": ["reciprocate"], "-6.8 3.7 3.4": ["followup"], "5.3 3.6 38.0": ["cranberry"], "15.4 3.6 14.5": ["glided"], "13.6 15.9 9.5": ["swivel"], "11.1 8.6 34.5": ["sprouts"], "1.5 4.0 0.1": ["archivist"], "-6.6 10.1 16.1": ["snowmobilers"], "0.7 -2.8 7.2": ["summonses"], "2.0 2.1 37.8": ["truffles"], "-0.5 12.8 9.6": ["grounders"], "7.7 7.8 15.2": ["billiards"], "0.6 15.2 -1.0": ["insofar"], "5.7 3.8 13.1": ["shoveled"], "-0.5 10.4 10.8": ["interrupts"], "10.2 9.5 10.3": ["wilt"], "11.6 1.0 8.4": ["residues"], "3.8 10.8 6.7": ["quantifiable"], "-3.2 9.2 4.5": ["reciprocity"], "4.2 9.1 3.0": ["galvanizing"], "-0.6 12.6 2.9": ["statesmen"], "-2.7 4.4 10.4": ["carpool"], "12.2 6.4 16.8": ["latte"], "2.4 4.1 1.6": ["demonstrable"], "-0.5 5.5 5.6": ["hurlers"], "-2.3 14.8 1.0": ["holster"], "15.2 8.3 9.8": ["howl"], "18.7 13.1 5.1": ["calamitous"], "5.4 23.1 15.4": ["smirk"], "-5.2 0.8 10.3": ["minimums"], "-0.4 8.2 -5.3": ["pager"], "9.5 10.8 -0.0": ["confiscating"], "24.9 9.4 14.1": ["voracious"], "-4.2 3.0 6.8": ["togethers"], "0.4 3.5 -5.3": ["vacating"], "-5.9 13.8 1.8": ["maltreatment"], "18.7 18.2 9.0": ["subterranean"], "11.3 20.1 4.3": ["holocaust"], "6.3 4.4 14.7": ["botanical"], "-2.3 9.6 5.5": ["preamble"], "0.4 5.9 12.3": ["vial"], "8.7 -5.0 7.7": ["biannual"], "7.3 25.0 11.3": ["reflex"], "-7.3 11.3 10.2": ["handicapper"], "-5.2 30.6 14.5": ["ordnance"], "12.8 5.2 1.9": ["cradled"], "12.4 8.3 28.3": ["molasses"], "-1.2 5.0 9.0": ["markdowns"], "3.0 13.3 15.2": ["antigen"], "-8.6 2.7 -1.7": ["confers"], "26.3 8.8 7.4": ["vibrating"], "6.4 9.3 9.4": ["masculinity"], "3.1 10.9 4.8": ["expletives"], "4.0 13.0 3.4": ["instigate"], "4.3 9.2 3.2": ["illegality"], "-2.3 13.2 3.4": ["foreseeable"], "9.1 12.5 7.2": ["inane"], "-2.2 24.7 2.8": ["overthrowing"], "12.4 5.6 8.7": ["stocky"], "6.7 20.5 8.7": ["sternly"], "15.3 9.1 31.4": ["beaver"], "-12.3 7.2 5.9": ["recidivism"], "-1.7 9.3 2.3": ["commemorations"], "4.9 4.0 9.7": ["headband"], "-0.4 14.2 13.4": ["gamesmanship"], "-0.9 7.4 16.6": ["taverns"], "15.8 17.1 7.9": ["riddle"], "-2.3 6.7 20.0": ["fertilization"], "7.3 14.7 1.1": ["agitators"], "-2.7 5.5 -3.2": ["impactful"], "10.7 12.6 6.1": ["optimists"], "5.7 21.4 -3.0": ["extinguishing"], "12.9 -5.7 11.6": ["wraparound"], "12.1 12.7 8.4": ["crackling"], "4.5 3.6 17.8": ["medallion"], "19.0 3.0 13.3": ["elongated"], "7.3 15.6 11.4": ["catchphrase"], "4.4 3.7 11.5": ["revelry"], "0.5 23.3 -1.4": ["destabilization"], "11.2 20.0 9.1": ["calamities"], "9.4 -3.1 2.0": ["makeovers"], "15.6 21.8 7.3": ["hellish"], "7.6 15.6 19.4": ["spamming"], "12.8 15.8 0.5": ["megaphone"], "-3.3 2.1 3.5": ["emulation"], "-2.5 13.9 6.2": ["offends"], "12.8 8.5 13.6": ["souring"], "4.2 1.8 23.0": ["silvers"], "6.3 11.5 0.5": ["pores"], "6.3 12.8 -0.2": ["confining"], "-1.0 14.2 10.4": ["policyholder"], "-2.3 2.9 7.1": ["workmanship"], "9.7 7.9 3.7": ["mutilation"], "1.0 10.4 3.8": ["chronology"], "6.5 11.6 3.1": ["nozzle"], "4.9 -2.1 24.2": ["loaves"], "-8.7 14.9 6.5": ["empathetic"], "-8.6 4.9 -1.4": ["foreword"], "7.4 18.6 6.8": ["miserably"], "11.1 10.8 3.0": ["trackers"], "10.2 14.7 9.1": ["berm"], "10.2 7.3 14.3": ["showy"], "12.9 8.2 13.6": ["plucking"], "-6.1 6.4 1.8": ["suiting"], "1.7 -4.2 -1.3": ["scammed"], "1.2 3.4 4.1": ["coronary"], "9.1 -5.2 0.4": ["roomy"], "7.2 27.6 10.7": ["projectile"], "20.3 4.6 3.8": ["premarket"], "14.1 8.1 12.8": ["wariness"], "8.2 10.8 4.7": ["spouting"], "3.1 12.2 7.2": ["cadence"], "15.7 11.5 9.3": ["pierce"], "7.0 16.1 3.0": ["cornering"], "3.8 22.8 6.3": ["healer"], "7.6 2.8 8.0": ["scalps"], "2.4 10.1 5.6": ["tradable"], "5.1 14.8 -3.0": ["fomenting"], "5.3 -4.4 -1.0": ["delved"], "13.4 29.9 9.2": ["madman"], "9.9 16.2 9.8": ["shifty"], "-0.1 5.9 6.3": ["licensors"], "15.3 1.0 5.8": ["dabbling"], "1.6 6.7 1.3": ["proclamations"], "-0.6 6.1 14.1": ["churchgoers"], "3.1 11.1 2.4": ["levying"], "1.6 2.8 -1.8": ["miscarriages"], "5.0 0.9 -4.2": ["trekked"], "18.8 29.2 24.4": ["devils"], "11.4 8.5 23.3": ["lilies"], "14.9 4.0 4.9": ["scion"], "-2.0 21.4 0.9": ["avenging"], "-5.7 12.8 4.3": ["overreact"], "8.2 7.6 26.0": ["tugboat"], "-2.5 9.2 4.5": ["hijab"], "19.4 4.9 11.6": ["nary"], "6.9 -0.2 0.7": ["renegotiating"], "9.4 11.3 8.3": ["blunted"], "12.3 8.9 5.4": ["tantrum"], "-5.0 5.4 5.9": ["invitees"], "6.4 33.0 4.1": ["antagonist"], "20.6 5.9 0.1": ["dispenser"], "1.5 10.2 4.2": ["iterations"], "12.8 18.1 2.5": ["cataclysmic"], "-2.5 7.9 -2.9": ["misrepresentations"], "-10.2 -3.9 7.2": ["townhomes"], "10.8 -1.7 4.1": ["pep"], "11.4 2.3 3.4": ["robustly"], "-0.4 6.3 1.5": ["backtrack"], "4.7 3.3 4.9": ["typified"], "-2.4 6.9 17.6": ["cuisines"], "-5.0 -1.0 -2.2": ["transcribed"], "-1.3 6.9 5.4": ["aerobic"], "16.4 11.5 8.1": ["splattered"], "4.0 15.3 2.8": ["jeeps"], "8.0 6.5 25.4": ["surfboard"], "2.0 13.4 -0.5": ["engrossing"], "18.2 6.9 4.5": ["schoolgirls"], "2.5 15.8 11.2": ["licks"], "2.7 12.9 -2.3": ["missive"], "2.7 11.3 5.2": ["unwritten"], "-5.4 11.3 6.0": ["aristocratic"], "8.6 3.3 5.9": ["shakedown"], "-6.6 -2.3 -5.0": ["acquit"], "12.3 8.8 9.7": ["tugging"], "4.7 21.6 9.5": ["willpower"], "8.5 10.8 12.2": ["childlike"], "7.0 12.2 5.3": ["unexplored"], "10.8 24.9 7.4": ["unspeakable"], "4.7 7.1 25.1": ["moorings"], "-5.3 4.2 3.6": ["signers"], "3.3 8.7 9.7": ["webmaster"], "6.3 1.6 12.7": ["glassware"], "1.3 2.6 12.7": ["neediest"], "-4.3 7.9 24.0": ["paddlers"], "3.4 8.2 5.2": ["engendered"], "1.6 9.8 -0.1": ["zonal"], "-8.0 2.6 2.0": ["annulment"], "6.4 8.4 1.4": ["retrain"], "1.5 4.2 8.0": ["statistician"], "0.1 24.6 6.3": ["ideologues"], "17.2 16.4 16.8": ["petrified"], "7.3 11.6 4.2": ["luckiest"], "1.2 5.7 20.0": ["skateboarders"], "13.4 4.2 6.1": ["drooling"], "6.7 13.2 4.3": ["walkthrough"], "7.2 12.4 16.7": ["petals"], "-3.6 5.7 14.9": ["sorghum"], "16.8 30.2 10.4": ["demonic"], "2.0 12.4 4.7": ["undeserved"], "0.7 5.2 -1.4": ["obituaries"], "1.4 5.1 20.3": ["paddled"], "7.1 1.3 7.9": ["electronica"], "7.2 -0.7 14.8": ["sequins"], "1.3 12.9 5.0": ["sayings"], "9.8 5.1 13.8": ["saws"], "11.7 0.2 4.5": ["outstrip"], "-2.5 11.5 1.8": ["rewind"], "7.2 15.1 3.2": ["mocks"], "21.6 11.4 6.2": ["simulates"], "11.9 4.1 7.8": ["stagnating"], "4.5 5.4 21.4": ["potluck"], "2.9 20.7 9.2": ["conspire"], "3.0 -1.3 6.9": ["pianos"], "15.8 13.8 3.1": ["eerily"], "-8.2 9.8 2.4": ["theologian"], "6.2 9.8 10.9": ["astonishment"], "12.4 9.0 8.1": ["supercomputers"], "3.9 11.8 28.3": ["mooring"], "10.3 11.7 7.5": ["irrepressible"], "-1.7 12.1 7.4": ["workaholic"], "17.5 7.9 -1.4": ["vandalizing"], "-7.9 4.6 0.8": ["debug"], "-0.7 -0.6 -2.8": ["prepay"], "-4.9 2.3 0.6": ["pathologists"], "16.6 17.3 9.2": ["foreboding"], "7.1 5.7 13.4": ["finely"], "18.6 14.4 31.5": ["rooster"], "3.9 0.1 11.9": ["tanned"], "6.0 8.2 23.7": ["frosting"], "4.0 10.8 25.8": ["doe"], "16.1 7.8 12.2": ["crayons"], "-2.2 5.3 1.3": ["marketability"], "16.8 7.1 15.7": ["excrement"], "12.3 10.4 4.3": ["rejoiced"], "-3.9 15.5 -2.2": ["commandant"], "6.1 4.9 8.2": ["fullness"], "-1.3 4.5 -1.7": ["experiential"], "-0.2 10.9 0.6": ["thoroughfares"], "5.2 7.0 12.9": ["campy"], "-0.7 19.8 10.6": ["nobility"], "-0.3 7.4 2.8": ["induces"], "4.6 5.0 1.5": ["unionize"], "-13.6 1.6 8.9": ["absentees"], "8.8 7.8 10.8": ["sharemarket"], "4.1 -0.4 4.9": ["outgrowth"], "6.7 13.8 8.1": ["steely"], "8.7 14.4 11.2": ["shading"], "8.1 15.8 2.2": ["dirtiest"], "12.6 19.6 6.9": ["colonized"], "10.2 9.6 7.8": ["dashes"], "-3.7 4.5 6.9": ["quibble"], "2.4 5.5 17.5": ["yachting"], "-2.6 10.7 2.0": ["bearable"], "-11.2 12.0 1.2": ["preface"], "-0.9 4.4 7.9": ["dosages"], "13.2 8.8 16.2": ["snagging"], "10.1 5.8 14.2": ["kitsch"], "15.0 18.2 10.5": ["brazenly"], "-7.9 4.9 5.9": ["tenured"], "-2.0 8.3 8.1": ["leanings"], "3.8 14.1 15.5": ["bro"], "2.0 13.5 6.3": ["habitually"], "19.7 20.1 10.3": ["extraterrestrial"], "7.2 7.5 15.7": ["calligraphy"], "13.8 1.3 8.9": ["trams"], "-5.3 10.1 7.3": ["inequity"], "12.7 24.5 5.8": ["everlasting"], "8.5 -4.2 8.4": ["preps"], "-5.9 9.1 -3.4": ["resourced"], "18.1 6.0 6.4": ["workmen"], "4.4 3.9 2.8": ["compulsive"], "10.5 7.4 9.1": ["conveyor"], "-0.1 12.1 1.0": ["consoled"], "9.1 22.6 12.5": ["maxim"], "9.7 8.0 18.6": ["seafront"], "3.0 23.9 7.1": ["sinners"], "-7.5 11.0 22.9": ["watercraft"], "10.4 2.7 10.3": ["whimper"], "3.5 5.5 11.3": ["ported"], "9.5 13.5 5.6": ["reinsurer"], "4.3 7.2 3.5": ["misdirected"], "-1.8 2.4 11.9": ["cleanups"], "6.7 -1.3 11.9": ["baroque"], "4.1 3.8 11.8": ["shekels"], "-9.0 -1.3 -0.6": ["tutored"], "4.1 15.4 3.7": ["uprooting"], "5.0 5.6 0.9": ["usurped"], "7.7 8.0 13.7": ["quartz"], "15.7 1.2 4.6": ["cushy"], "-1.0 4.1 -9.7": ["ambit"], "2.0 14.2 7.1": ["straights"], "12.6 9.0 11.4": ["stagger"], "2.1 6.0 3.0": ["hemoglobin"], "15.5 9.6 5.9": ["implode"], "5.0 10.3 12.4": ["bummer"], "13.2 14.3 4.7": ["mirage"], "15.8 7.3 24.0": ["sponges"], "22.4 11.8 0.5": ["hurtling"], "9.5 14.7 12.1": ["tombstone"], "-4.7 1.3 17.1": ["oxycodone"], "5.4 -3.2 16.1": ["waxing"], "7.2 10.8 4.8": ["bombastic"], "4.7 0.6 12.8": ["grunge"], "13.0 6.7 4.1": ["wildest"], "13.4 12.3 27.0": ["grizzly"], "8.1 5.6 17.7": ["gloved"], "-5.1 14.1 4.9": ["scriptures"], "5.4 7.5 0.3": ["pandemonium"], "4.5 2.0 6.8": ["mortgaged"], "6.5 2.0 10.5": ["knitted"], "2.8 9.1 9.7": ["kneecap"], "6.3 6.2 2.5": ["sullied"], "1.7 10.4 8.8": ["playmaking"], "-2.0 3.7 4.3": ["ph"], "0.8 7.1 2.6": ["centralization"], "-1.6 26.2 10.1": ["seduction"], "-0.4 3.6 4.9": ["amps"], "4.7 1.6 -3.8": ["jetting"], "9.2 19.0 8.0": ["recalcitrant"], "18.3 14.5 3.1": ["boldest"], "14.4 4.5 -2.6": ["leapfrogged"], "16.7 11.0 5.9": ["prowling"], "2.1 4.6 7.9": ["wining"], "-4.2 4.4 4.5": ["urology"], "5.2 8.1 2.7": ["egalitarian"], "-4.7 7.4 0.5": ["ascribed"], "1.1 3.4 24.1": ["foodies"], "6.9 13.8 10.9": ["hollered"], "3.5 9.0 4.8": ["narcissistic"], "15.1 3.9 12.0": ["extraordinaire"], "12.3 9.1 8.5": ["morass"], "1.6 13.7 8.3": ["amputations"], "15.2 2.7 6.1": ["outstripping"], "6.7 3.2 0.3": ["annul"], "17.0 9.1 23.5": ["puffy"], "2.8 15.7 0.6": ["hangars"], "-0.5 10.9 1.9": ["invokes"], "2.4 6.4 0.9": ["superseded"], "6.6 3.8 13.2": ["tinge"], "-5.0 3.2 -2.5": ["dependability"], "12.0 1.8 12.2": ["ca"], "6.9 16.6 17.3": ["midsection"], "5.5 11.6 29.2": ["grouse"], "16.5 -1.9 17.6": ["tubs"], "6.9 19.4 -4.3": ["hijacker"], "3.5 7.4 8.6": ["unskilled"], "-2.2 13.5 17.3": ["hashish"], "10.9 11.0 4.5": ["dexterity"], "9.2 5.4 6.0": ["optimistically"], "10.1 11.1 9.1": ["groans"], "-7.6 13.1 9.4": ["takedowns"], "13.4 9.1 19.5": ["snowflakes"], "2.5 14.4 8.0": ["overpasses"], "-10.9 1.0 10.5": ["furloughed"], "7.1 11.6 7.6": ["materialism"], "-3.4 5.5 18.5": ["malt"], "-4.4 9.7 4.7": ["trailhead"], "13.2 3.6 12.1": ["sag"], "10.4 14.4 9.7": ["wanton"], "11.5 27.3 4.9": ["viciously"], "2.7 10.0 7.9": ["grandfathers"], "16.9 3.2 10.7": ["salivating"], "7.3 15.1 7.7": ["fissures"], "-1.0 23.1 5.0": ["obedient"], "-7.9 19.3 2.3": ["indoctrination"], "4.2 10.2 1.5": ["roused"], "12.0 9.8 -2.2": ["refocusing"], "-4.2 2.0 13.3": ["gilts"], "9.3 -2.7 15.5": ["dreadlocks"], "16.7 11.2 12.0": ["backwater"], "18.8 12.4 7.6": ["thrusting"], "16.3 18.6 34.9": ["crickets"], "0.6 7.3 12.7": ["refractory"], "3.3 4.1 5.6": ["spanked"], "-3.8 3.3 2.9": ["ibuprofen"], "10.8 9.7 12.5": ["chimneys"], "0.9 8.5 11.0": ["nourish"], "6.4 -1.0 4.7": ["outperformance"], "7.9 4.4 4.4": ["cataloging"], "2.6 7.6 3.7": ["comer"], "0.4 3.8 6.1": ["carols"], "-1.8 14.9 2.3": ["subtitle"], "5.9 5.0 14.0": ["gondola"], "12.7 12.0 18.2": ["tugs"], "1.6 20.0 6.1": ["indescribable"], "6.2 -2.3 5.2": ["buttoned"], "8.5 10.2 10.9": ["shepherds"], "6.8 6.5 31.0": ["almond"], "11.7 16.1 2.0": ["riskiest"], "0.8 8.4 9.5": ["pathos"], "12.0 1.0 7.2": ["mothballed"], "3.9 11.0 3.3": ["contingents"], "3.7 11.7 29.3": ["mangroves"], "3.0 4.6 7.5": ["recyclers"], "8.6 -3.6 0.5": ["informatics"], "-2.8 -2.2 -0.5": ["convenor"], "9.4 0.7 5.7": ["recouping"], "-1.3 4.5 12.1": ["spaceflight"], "18.0 12.6 9.2": ["vista"], "17.0 1.1 9.2": ["jingle"], "11.6 8.3 20.5": ["parrots"], "5.3 8.4 6.2": ["postmaster"], "-2.9 13.6 26.3": ["beekeepers"], "0.6 1.0 7.3": ["washout"], "10.0 17.8 4.9": ["rearguard"], "11.7 7.2 2.6": ["flaps"], "-2.6 7.8 7.3": ["underinsured"], "7.1 6.7 5.2": ["insensitivity"], "0.9 9.0 9.5": ["contentment"], "6.6 10.1 10.4": ["revels"], "-5.7 6.0 8.5": ["enablement"], "-0.2 1.3 -0.5": ["leasehold"], "2.1 -3.1 16.4": ["simmered"], "14.2 10.1 3.6": ["nipping"], "12.7 10.8 9.2": ["cuddle"], "4.9 8.7 9.8": ["punctuation"], "2.1 11.2 7.3": ["precursors"], "14.0 6.7 18.0": ["placid"], "1.6 6.9 4.5": ["augmenting"], "0.0 13.8 8.9": ["retort"], "7.0 9.0 11.7": ["connoisseurs"], "-0.8 8.3 9.8": ["platitudes"], "2.8 8.2 6.1": ["flout"], "4.7 8.4 17.6": ["southernmost"], "-2.6 2.6 11.2": ["bohemian"], "3.2 3.3 -0.3": ["remiss"], "2.4 6.1 7.6": ["antsy"], "9.8 9.7 35.6": ["caribou"], "5.5 6.2 13.0": ["genial"], "4.6 9.0 -1.5": ["decode"], "-4.1 9.0 7.6": ["deleveraging"], "8.2 12.6 6.6": ["fluidity"], "1.8 1.6 1.3": ["salacious"], "-5.9 9.8 21.5": ["birding"], "4.2 7.4 2.3": ["quotient"], "4.7 6.8 -1.7": ["castigated"], "8.7 -1.2 7.8": ["washers"], "1.9 6.6 12.5": ["coals"], "11.0 3.4 5.7": ["skirting"], "-7.7 11.7 4.5": ["interred"], "1.8 10.4 12.6": ["coolant"], "3.4 14.6 1.9": ["intrinsically"], "3.2 -1.6 6.5": ["checkups"], "8.3 1.7 58.4": ["mackerel"], "3.9 17.5 11.4": ["redrawn"], "3.5 14.0 12.9": ["jock"], "13.4 5.8 4.8": ["bungling", "frogmarching"], "15.3 4.4 3.2": ["companywide"], "2.8 -4.0 -0.1": ["letterhead"], "4.3 3.0 -0.4": ["voids"], "7.3 2.4 -1.5": ["imploring"], "7.4 -1.2 7.6": ["jumpsuit"], "-3.2 3.5 30.4": ["mangoes"], "2.5 19.6 4.5": ["scapegoats"], "10.5 11.2 8.7": ["counterbalance"], "3.9 -6.3 2.2": ["conservator"], "1.8 11.2 22.8": ["seared"], "7.0 12.8 14.3": ["hilariously"], "-2.1 6.3 9.1": ["reprising"], "-7.6 9.2 4.4": ["deviated"], "19.5 8.5 19.4": ["mouthful"], "18.7 9.6 7.5": ["bizarrely"], "2.1 7.7 4.3": ["tantrums"], "9.8 7.4 11.7": ["pretzels"], "8.5 19.3 23.5": ["frigate"], "9.3 2.2 13.1": ["wad"], "2.3 13.1 6.5": ["awkwardness"], "-5.2 12.7 18.9": ["officeholders"], "-4.1 4.5 3.0": ["fingerprinted"], "8.5 4.7 9.4": ["extravagance"], "-2.3 7.0 6.6": ["ratifying"], "4.5 5.3 7.7": ["degenerate"], "-1.3 7.6 5.6": ["videographer"], "10.9 12.5 5.6": ["hanger"], "-0.7 8.1 24.6": ["foodie"], "-4.5 2.9 7.3": ["hairstyles"], "12.3 4.2 12.7": ["jacking"], "2.6 1.4 7.5": ["resins"], "9.1 6.2 9.1": ["hawkers"], "14.7 8.5 8.2": ["cranks"], "11.0 1.4 9.6": ["sheared"], "-2.7 13.3 2.9": ["rebelled"], "10.0 9.3 7.3": ["righted"], "-3.6 5.5 5.4": ["featurette"], "-2.3 6.0 2.8": ["hypnosis"], "5.2 4.2 5.4": ["refreshment"], "-0.5 9.8 1.5": ["politicization", "exogenous"], "8.6 22.4 10.7": ["foolhardy"], "6.0 15.7 2.5": ["intrigues"], "16.3 13.0 11.2": ["clump"], "3.2 2.0 4.3": ["hotelier"], "2.2 3.9 3.7": ["invoicing"], "9.0 3.0 6.0": ["hauler"], "-0.1 6.6 7.0": ["aneurysm"], "6.9 15.6 6.9": ["precipitate"], "7.4 18.7 19.4": ["fleas"], "17.4 -2.6 13.9": ["crested"], "-3.3 2.2 3.4": ["admittance"], "14.9 22.7 12.8": ["werewolf"], "6.9 8.9 7.4": ["reshuffling"], "4.0 6.3 16.3": ["decking"], "3.5 15.2 3.1": ["exalted"], "8.7 6.2 17.7": ["napkin"], "6.0 2.2 6.6": ["nervy"], "5.7 5.9 4.0": ["dissolves"], "16.9 -2.1 4.4": ["careened"], "3.4 14.5 -2.5": ["eject"], "0.0 11.6 5.0": ["mismatches"], "-0.6 15.8 -1.0": ["democratically"], "-7.8 8.7 2.8": ["enumerated"], "-4.8 17.0 2.2": ["nonviolence"], "-7.0 4.1 9.2": ["downstate"], "9.7 12.3 -0.5": ["blot"], "6.4 11.8 23.8": ["seawall"], "13.5 3.6 6.1": ["abounds"], "17.8 16.4 9.6": ["joystick"], "12.3 -0.2 7.7": ["tele"], "17.6 14.0 36.8": ["pea"], "2.5 13.6 0.8": ["diatribe"], "10.4 5.7 4.5": ["foreshadowed"], "6.6 10.9 4.1": ["expropriation"], "-0.4 20.1 -0.6": ["expedient"], "13.1 4.8 20.5": ["yoghurt"], "11.7 12.8 8.2": ["screeching"], "-2.5 10.0 8.5": ["repossession"], "-6.4 8.9 9.1": ["delineated"], "3.3 6.0 1.2": ["newswire"], "12.0 15.1 13.2": ["pulverized"], "11.4 6.5 12.5": ["lethargy"], "3.9 2.1 -1.9": ["pacemakers"], "-5.0 3.5 3.1": ["celibacy"], "-9.2 9.1 5.5": ["irrigate"], "1.5 9.5 8.7": ["explosiveness"], "3.2 6.4 4.7": ["handlebars"], "-2.2 10.6 8.3": ["cornea"], "-2.7 8.7 4.8": ["idolized"], "2.3 8.1 5.9": ["repeatable"], "-3.2 19.0 -3.7": ["selflessness"], "31.2 1.8 18.8": ["oversize"], "-2.9 7.1 0.7": ["prerequisites"], "-0.9 11.4 10.5": ["incompletion"], "3.3 6.4 10.0": ["pimps"], "-6.0 12.5 4.3": ["eloquence"], "6.0 5.2 3.4": ["bootleg"], "20.4 0.5 8.9": ["rippled"], "6.4 2.9 6.7": ["bronchitis"], "-3.0 9.2 -0.1": ["evidences"], "4.8 10.4 0.3": ["carcinogens"], "2.5 -0.5 7.4": ["metered"], "6.0 -2.1 0.5": ["lavished"], "4.3 20.0 6.5": ["immobilized"], "-1.9 25.9 5.5": ["pacifist"], "9.7 23.5 3.9": ["kinetic"], "6.0 23.2 -1.0": ["maliciously"], "0.5 8.8 7.0": ["overreacting"], "-12.6 3.0 7.2": ["musicianship"], "8.0 10.5 5.0": ["swipes"], "12.1 -0.5 5.6": ["bespectacled"], "-1.9 4.0 2.3": ["physiotherapist"], "4.0 10.9 6.8": ["rotor"], "3.8 2.5 7.9": ["overdoses"], "11.3 6.5 1.7": ["unmanageable"], "6.0 14.6 14.7": ["gunpowder"], "-3.4 8.1 10.7": ["transponder"], "0.6 11.1 4.4": ["contentions"], "6.6 5.1 16.6": ["whimsy"], "10.6 5.8 25.6": ["nautical"], "8.4 -6.4 9.3": ["kickstart"], "-1.9 3.1 7.1": ["reconciliations"], "7.2 3.6 3.1": ["verve"], "2.6 18.4 2.4": ["imprison"], "0.3 5.8 32.4": ["orchid"], "6.5 14.6 10.3": ["imperious"], "4.0 3.9 2.1": ["asphyxiation"], "7.9 -5.5 14.0": ["tapering"], "3.8 2.9 3.4": ["duct"], "3.6 2.5 13.0": ["halfpipe"], "8.8 12.2 14.6": ["politicos"], "1.4 5.8 11.5": ["snarky"], "-1.0 5.2 2.4": ["lf"], "6.6 1.0 5.9": ["afp"], "4.7 22.1 6.2": ["puncher"], "-1.0 4.1 13.2": ["isotopes"], "-0.1 9.0 8.6": ["inebriated"], "9.4 11.8 8.7": ["mending"], "5.9 13.1 3.0": ["electrocution"], "18.4 13.8 0.9": ["triumphantly"], "15.9 8.7 24.9": ["nibble"], "10.0 2.0 11.8": ["slurry"], "6.9 7.7 -2.1": ["engrossed"], "0.6 7.9 3.0": ["cliffhanger"], "-2.6 4.6 11.0": ["amphetamine"], "2.1 52.7 10.1": ["aggressors"], "23.2 3.3 15.1": ["beefy"], "7.6 4.8 6.5": ["grumble"], "-2.8 11.4 8.4": ["oxidation"], "-1.6 9.8 13.2": ["biathlon"], "11.4 -0.6 -8.9": ["lauding"], "6.2 17.1 8.4": ["guile"], "-2.0 4.0 9.6": ["surmised"], "18.9 14.7 11.8": ["antennae"], "5.0 10.3 4.0": ["homelands"], "2.7 8.9 26.2": ["tulips"], "4.2 16.5 22.8": ["typhoons"], "2.2 2.6 3.5": ["eczema"], "1.8 5.8 6.0": ["naps"], "4.7 1.2 1.5": ["consul"], "-5.4 0.5 4.6": ["abstention"], "3.8 25.7 4.6": ["airbase"], "3.6 8.8 10.0": ["bridesmaids"], "9.9 7.7 9.3": ["sockets"], "4.5 7.7 -1.7": ["ergonomics"], "0.4 -1.5 7.2": ["rulemaking", "mcm"], "4.1 43.5 -0.8": ["mujahedeen"], "18.9 7.4 10.9": ["interlocking"], "11.7 17.9 9.7": ["parable"], "2.6 1.4 9.2": ["grooms"], "19.0 -4.0 -1.5": ["fourfold"], "2.6 10.8 2.2": ["relevancy"], "5.4 11.8 13.6": ["contaminant"], "2.4 18.1 0.1": ["tolerating"], "4.8 8.9 5.0": ["spout"], "5.8 0.4 2.8": ["chime"], "-3.9 9.8 11.3": ["transceiver"], "-4.6 7.2 4.2": ["neurosurgery"], "19.0 6.9 6.0": ["delist"], "16.6 10.9 6.4": ["boundless"], "5.6 13.1 5.8": ["offstage"], "6.5 9.2 -3.0": ["backtracking"], "3.8 6.0 12.5": ["headgear"], "17.6 12.8 6.6": ["babes"], "13.5 13.3 25.5": ["rainbows"], "7.5 7.3 -4.3": ["conduits"], "5.9 6.1 3.2": ["shareholdings"], "-6.1 6.7 6.9": ["overrides"], "-0.7 3.5 11.5": ["barangays"], "15.7 6.0 8.4": ["cocoon"], "-6.4 11.2 0.5": ["productively"], "14.2 14.5 12.9": ["helplessly"], "-3.2 10.6 14.1": ["consecrated"], "11.7 -0.7 2.7": ["august"], "-1.4 1.0 4.5": ["hygienic"], "5.2 10.2 7.5": ["motorways"], "-6.0 7.6 7.4": ["duals"], "6.3 6.8 1.0": ["accesses"], "16.8 9.0 15.5": ["writhing"], "-2.0 3.2 11.6": ["floodplain"], "9.4 15.7 16.0": ["redneck"], "6.8 11.2 3.8": ["usurp"], "-7.2 9.1 2.1": ["sepsis", "issuable"], "10.2 18.3 12.6": ["lunging"], "0.7 11.1 7.8": ["underappreciated"], "7.2 11.1 3.8": ["playboy"], "1.0 4.5 35.3": ["cilantro"], "15.1 17.2 6.7": ["dummies"], "6.9 14.4 4.8": ["manipulations"], "14.7 3.9 10.8": ["lurched"], "11.5 0.5 17.2": ["tacking"], "15.6 28.5 13.7": ["bastards"], "-8.0 1.1 -0.4": ["concurs"], "5.1 -4.2 1.8": ["dryers"], "3.1 3.9 7.9": ["scrolls"], "16.6 2.7 2.6": ["liken"], "10.3 6.9 60.7": ["prawns"], "7.5 -0.5 7.4": ["congregated"], "12.0 17.0 8.6": ["suffocate"], "6.0 5.9 8.5": ["mortified"], "2.4 5.2 -0.0": ["terming"], "16.5 15.0 15.4": ["meteor"], "0.4 14.5 0.5": ["defecting"], "4.4 -0.3 -1.5": ["improprieties"], "6.8 24.0 6.2": ["obstructions"], "12.3 2.2 8.6": ["overalls"], "0.5 15.2 5.8": ["unfiltered"], "1.7 10.4 8.9": ["lessens"], "21.2 11.3 3.7": ["swathe"], "8.4 10.6 9.8": ["environmentalism"], "27.8 12.4 10.9": ["swooping"], "6.3 5.4 13.0": ["zipper"], "6.0 10.2 5.1": ["alarmist"], "-3.2 12.5 3.7": ["deprives"], "46.8 10.7 17.5": ["behemoths"], "10.0 12.7 13.9": ["subsurface"], "5.6 4.3 5.8": ["memento"], "8.2 1.7 2.0": ["pictorial"], "1.9 10.1 1.9": ["unencumbered"], "1.9 11.6 8.6": ["divinity"], "9.8 14.5 14.9": ["blizzards"], "17.6 7.9 11.7": ["cola"], "4.7 23.1 4.3": ["messengers"], "2.9 4.2 1.8": ["laundered"], "5.1 31.8 9.3": ["neocons"], "13.0 12.6 1.0": ["ceasing"], "5.3 13.1 8.9": ["abode"], "2.0 9.2 11.4": ["grassland"], "11.2 2.3 0.1": ["defaced"], "0.7 0.6 2.5": ["flouted"], "-3.6 3.3 10.0": ["sax"], "3.1 5.9 4.4": ["porting"], "-5.3 5.5 7.8": ["mannered"], "2.2 16.8 8.7": ["inaccuracy"], "7.6 21.1 6.8": ["loathed"], "8.8 12.3 17.4": ["iris"], "3.6 11.6 1.1": ["diffusion"], "-2.6 2.0 7.8": ["repossessions"], "12.3 8.6 6.2": ["unimpeded"], "-3.6 -5.8 9.3": ["liposuction"], "11.6 9.2 2.4": ["ignites"], "17.2 5.7 2.7": ["gouged"], "1.4 11.2 2.4": ["trite"], "-3.4 0.6 6.7": ["modulation"], "1.9 10.6 29.7": ["rosemary"], "11.5 5.5 4.8": ["dotting"], "1.5 16.5 1.5": ["furtherance"], "5.3 -0.9 -2.0": ["repackaged"], "7.7 2.6 2.9": ["sexier"], "5.3 4.9 5.6": ["scoping"], "22.5 9.6 7.9": ["fluttering"], "-4.8 -1.2 10.3": ["extracurricular"], "5.8 0.9 5.1": ["speeded"], "9.5 13.3 -0.5": ["detach"], "7.0 -4.7 -1.9": ["shepherded"], "5.8 5.3 13.6": ["mated"], "6.5 6.1 2.9": ["jostled"], "6.9 9.2 5.2": ["unsettle"], "13.7 12.7 4.9": ["utopian"], "29.3 4.7 7.7": ["dynamo"], "-8.1 5.2 3.4": ["debugging"], "1.1 7.2 7.7": ["laceration"], "1.4 8.4 18.8": ["firework"], "0.8 2.0 9.0": ["ecologically"], "5.4 4.0 6.0": ["thrifty"], "2.7 9.0 10.0": ["cataracts"], "4.1 20.6 4.1": ["marginalize"], "-6.0 9.3 5.2": ["moto"], "7.6 7.4 -0.5": ["hitmaker"], "5.3 1.7 4.9": ["es"], "-6.9 16.6 -1.8": ["answerable"], "18.9 -0.6 18.5": ["frothy"], "-6.5 4.3 9.4": ["deliverables"], "6.6 4.1 0.5": ["standardizing"], "9.7 0.8 8.3": ["adobe"], "3.6 5.5 -0.1": ["arouse"], "-4.6 8.1 6.8": ["mw"], "17.3 24.2 22.5": ["bot"], "13.7 3.5 0.6": ["tortuous"], "8.0 13.0 5.1": ["stonewalling"], "6.2 10.8 16.9": ["slacker"], "11.8 8.1 4.1": ["overstating"], "9.0 9.3 11.5": ["pegging"], "3.5 15.3 5.7": ["dispersing"], "7.6 7.0 17.0": ["mushy", "affectionally"], "0.5 13.3 9.6": ["reinsurers"], "2.6 -4.5 2.0": ["reimbursing"], "11.6 -2.2 -2.4": ["technologist"], "7.2 3.9 5.6": ["stagnate"], "-5.8 0.3 -5.6": ["liaise"], "13.7 16.0 5.5": ["vestiges"], "19.0 16.1 4.6": ["vortex"], "10.7 14.8 -0.4": ["emitter"], "5.4 -0.1 1.0": ["fondled"], "-6.3 0.1 -0.1": ["neonatal"], "19.3 25.9 18.5": ["bots"], "5.4 5.3 2.2": ["eagled"], "-8.0 10.8 3.2": ["predictors"], "-5.0 12.8 22.4": ["faceoffs"], "1.5 3.0 6.7": ["leach"], "3.9 10.2 10.2": ["comets"], "14.1 6.7 21.7": ["rhinos"], "-3.6 8.3 2.1": ["transact"], "8.0 -0.3 4.6": ["unopened"], "6.3 11.6 4.0": ["whats"], "19.5 15.4 29.4": ["slimy"], "-9.8 6.0 6.1": ["seminaries"], "-1.3 11.3 10.0": ["conveyance"], "19.3 4.6 9.1": ["wobbled"], "5.5 10.7 -1.2": ["flirtation"], "9.0 4.6 9.3": ["goof"], "-7.2 10.9 0.7": ["deviations"], "-2.6 5.0 6.8": ["jeopardizes"], "7.4 7.0 12.8": ["subsides"], "-0.2 8.0 0.0": ["realigned"], "-7.8 3.9 4.3": ["holdovers"], "1.8 5.9 10.2": ["thrifts"], "0.2 8.4 11.0": ["wagered"], "-5.5 14.3 8.9": ["interpersonal"], "5.5 10.6 -2.0": ["blasphemous"], "8.6 14.9 9.4": ["glider"], "7.3 9.6 15.9": ["canes"], "7.9 38.7 5.0": ["guerilla"], "-6.3 13.6 6.5": ["curable"], "11.6 31.9 8.9": ["elemental"], "-0.6 8.1 5.7": ["delineate"], "-0.8 -0.4 0.6": ["pharmacology"], "16.3 3.2 9.0": ["kickback"], "9.1 15.3 15.6": ["boils"], "4.9 3.9 0.4": ["begrudge"], "6.8 19.8 7.7": ["subservient"], "27.1 17.3 15.9": ["devouring"], "-0.3 9.1 3.3": ["underused"], "18.0 20.6 15.4": ["slay"], "2.4 2.7 -1.6": ["unaccompanied"], "-6.6 -2.1 4.1": ["caseworkers"], "0.1 15.4 3.2": ["entrapment"], "10.0 17.7 9.8": ["surly"], "-0.2 3.9 -3.8": ["absolved"], "-1.9 9.5 7.5": ["sharia"], "9.0 9.0 0.9": ["cellulose"], "7.0 5.7 16.9": ["glacial"], "2.7 23.6 -1.3": ["enablers"], "15.0 13.4 3.5": ["cornfield"], "9.9 3.6 22.1": ["margarine"], "5.3 -2.1 7.9": ["chromium"], "9.9 -0.7 2.9": ["eschewed"], "15.5 1.7 14.2": ["rimmed"], "-7.2 10.0 5.7": ["byes"], "3.2 5.7 -2.8": ["resonant"], "-2.4 -0.8 2.4": ["attendances"], "-8.6 8.4 3.8": ["verbatim"], "6.2 19.0 5.5": ["bigot"], "4.6 11.6 11.5": ["sunburn"], "5.9 9.6 14.1": ["newbies"], "6.1 7.6 9.8": ["dynasties"], "-3.1 15.2 -4.8": ["vitriolic"], "15.5 3.2 11.4": ["heaved"], "9.1 8.3 6.4": ["sketching"], "1.7 3.1 4.2": ["graphene"], "0.8 2.2 35.3": ["cranberries"], "14.8 12.8 -0.4": ["swastika"], "11.2 -0.8 -5.9": ["extolling"], "1.0 7.2 19.3": ["heirloom"], "15.1 8.0 14.3": ["streamers"], "5.3 13.4 6.6": ["revulsion"], "7.2 1.5 4.3": ["stadia"], "8.1 11.3 2.0": ["denotes"], "12.9 27.1 14.2": ["abomination"], "5.6 7.0 5.5": ["invigorated"], "7.7 -4.2 -2.1": ["swindled"], "11.6 13.5 0.5": ["incinerated"], "4.5 -0.6 14.2": ["carpenters"], "1.3 11.2 14.6": ["shtick"], "7.8 14.0 3.8": ["intoxicating"], "-0.2 5.2 2.9": ["hurdler"], "19.4 22.5 21.8": ["locusts"], "-2.8 1.0 23.4": ["rebar"], "-5.0 13.9 -0.6": ["communicators"], "10.7 0.5 3.4": ["fillip"], "4.3 -4.0 1.6": ["walkouts"], "6.4 9.1 6.9": ["showdowns"], "-2.0 7.8 5.1": ["rigidity"], "5.6 25.1 7.9": ["arsenals"], "13.3 -2.8 -2.4": ["consortia"], "17.1 3.3 23.3": ["smorgasbord"], "10.8 2.0 0.1": ["reverberate"], "-5.9 12.4 10.5": ["parolee"], "0.2 3.1 9.3": ["bodybuilding"], "5.1 6.5 5.4": ["mixtures"], "-2.9 10.5 -2.1": ["condoning"], "5.5 22.4 4.1": ["deceitful"], "-8.6 6.8 6.3": ["microcontroller"], "4.5 -4.2 1.7": ["acceptances"], "10.0 4.6 8.0": ["nadir"], "14.5 2.0 14.5": ["balding"], "-3.5 2.2 4.0": ["interchanges"], "3.4 4.4 4.8": ["lackadaisical"], "6.4 2.8 15.4": ["smoothies"], "7.5 11.6 5.4": ["amuse"], "14.8 2.8 -0.8": ["rebrand"], "-6.7 -0.6 8.4": ["rehire"], "8.7 8.4 20.6": ["testicles"], "-2.6 10.9 9.1": ["formulaic"], "1.3 0.5 1.8": ["parlay"], "-5.7 9.7 15.6": ["handicapping"], "0.7 16.3 5.9": ["individualism"], "1.2 7.3 5.5": ["subtitled"], "-10.3 8.5 -1.7": ["screenplays"], "-4.5 10.1 1.3": ["correlations"], "5.6 17.3 16.5": ["tripod"], "-0.1 6.5 5.8": ["frugality"], "10.3 4.4 12.2": ["divas"], "15.3 -1.1 12.7": ["tins"], "7.2 4.8 8.3": ["rambunctious"], "14.0 11.4 1.6": ["colluding"], "4.5 15.0 4.6": ["eavesdrop"], "4.5 4.5 4.8": ["bedridden"], "5.5 10.8 9.4": ["fave"], "0.6 5.4 13.3": ["jackpots"], "-1.0 12.4 4.4": ["antimicrobial"], "-1.1 -1.8 6.1": ["sukuk"], "-4.4 6.1 -0.5": ["arsons"], "9.0 0.5 3.9": ["slates"], "12.8 6.6 18.5": ["planter"], "4.8 -1.8 5.5": ["headroom"], "-0.4 12.2 14.0": ["deadpan"], "0.5 -6.9 1.4": ["postponements"], "2.4 22.6 3.9": ["heresy"], "-4.6 3.1 5.4": ["expediting"], "4.8 4.8 7.1": ["reproductions"], "6.2 12.5 8.3": ["weatherman"], "1.4 14.2 2.2": ["confuses"], "8.1 13.0 10.9": ["domesticated"], "12.4 0.8 4.2": ["revises"], "-1.2 8.5 6.7": ["immunology"], "14.9 10.1 34.0": ["plankton"], "6.3 7.2 1.7": ["nameplate"], "1.3 20.6 6.2": ["landmine"], "8.6 -2.9 -5.5": ["jetted"], "-6.0 -0.8 9.4": ["licensure"], "12.4 1.7 29.1": ["burrito"], "8.6 2.6 16.0": ["graying"], "4.2 5.4 22.4": ["packers"], "2.0 4.9 22.7": ["migratory"], "2.2 9.3 6.4": ["disapproving"], "10.0 13.3 12.1": ["magicians", "securitisers"], "3.1 7.6 1.3": ["meteorology"], "0.9 3.9 8.8": ["pelvic"], "9.0 2.6 12.0": ["cashiers"], "4.6 6.8 6.4": ["windshields"], "3.5 1.9 5.1": ["overlaps"], "-3.7 8.5 2.6": ["abrasions"], "2.9 9.4 5.2": ["politicizing"], "0.0 13.1 14.8": ["neuter"], "24.3 -3.0 10.9": ["whirl"], "-8.2 16.5 11.0": ["hydrants"], "-5.5 17.6 9.2": ["probabilities"], "3.5 6.9 -0.1": ["useable"], "-2.6 6.7 3.1": ["ethnically"], "2.5 1.7 14.9": ["beachside"], "-10.2 11.9 -1.0": ["espouse"], "3.0 7.3 8.1": ["promiscuous"], "16.5 -0.7 14.5": ["stilts"], "15.7 14.3 28.4": ["beak"], "11.9 21.0 7.0": ["venomous"], "8.6 19.8 5.4": ["spotters"], "16.2 16.2 10.1": ["counterweight"], "2.4 11.7 10.6": ["fallback"], "11.1 10.0 10.7": ["envisioning"], "3.6 6.2 12.1": ["synth"], "16.0 17.4 8.5": ["swashbuckling"], "5.0 12.4 -1.5": ["undetectable"], "5.4 15.1 1.3": ["odious"], "5.5 4.7 35.5": ["lasagna"], "14.7 2.8 -3.7": ["supercharged"], "-9.3 10.0 -3.4": ["categorical"], "2.3 -2.6 21.3": ["banquets"], "8.6 2.0 19.9": ["pickers"], "7.0 4.8 24.4": ["veg"], "15.5 17.5 9.5": ["plundering"], "-0.2 20.8 4.3": ["brutalized"], "4.2 13.4 3.5": ["truer"], "-1.4 16.7 11.1": ["hydrant"], "5.8 3.4 14.2": ["homey"], "11.6 10.5 20.1": ["moonlight"], "3.3 0.4 5.6": ["longterm"], "7.5 16.7 11.1": ["countenance"], "3.4 6.7 3.3": ["bookshelves"], "11.6 12.2 -0.5": ["locator"], "7.4 25.8 5.3": ["sharpshooter"], "17.7 17.4 9.4": ["inexorably"], "7.1 3.1 16.9": ["socked"], "19.2 19.0 12.2": ["jerks"], "14.0 3.5 9.1": ["expensing"], "4.4 4.4 3.2": ["spasm"], "18.6 4.9 1.1": ["ubiquity"], "14.5 0.5 21.9": ["sawdust"], "9.3 6.3 7.4": ["fusing"], "-2.2 11.6 1.1": ["sobs"], "1.4 10.3 15.9": ["salts"], "1.3 5.6 9.0": ["noir"], "14.5 8.6 7.4": ["daredevil"], "10.5 0.8 4.6": ["vaulting"], "0.6 3.9 -3.3": ["refutes"], "8.3 1.3 3.0": ["statisticians"], "1.5 5.1 12.8": ["clunker"], "7.6 -1.3 8.5": ["bared"], "6.0 13.0 4.0": ["protons"], "-2.6 19.4 4.7": ["betrays"], "-6.8 1.5 42.7": ["chinook"], "11.2 -1.1 6.9": ["slimming"], "17.8 6.7 23.3": ["zebra"], "-4.5 -0.3 9.7": ["kgs"], "7.0 6.6 3.5": ["expectant"], "7.4 -4.5 10.5": ["janitorial"], "2.5 3.6 3.0": ["furthered"], "0.3 15.5 2.6": ["unkind"], "23.6 1.7 8.4": ["rippling"], "3.0 10.1 12.0": ["scrums"], "21.3 5.6 7.2": ["undulating"], "20.7 6.4 11.9": ["groaning"], "5.5 11.4 24.8": ["condiments"], "0.2 6.1 -0.2": ["abnormality"], "16.3 14.9 10.5": ["spook"], "-5.0 3.7 2.6": ["rehash"], "6.4 0.4 -2.0": ["reneging"], "-6.4 -3.0 8.3": ["caseworker"], "3.8 15.8 12.0": ["rapids"], "0.5 8.9 25.4": ["tapas"], "-6.9 9.1 2.6": ["theologians"], "10.8 3.3 6.2": ["songstress"], "7.1 7.3 13.6": ["exquisitely"], "3.6 5.6 -7.9": ["conveniences"], "2.7 9.8 0.2": ["traversed"], "11.0 13.4 11.5": ["ephemeral"], "19.4 -1.6 4.0": ["ballyhooed"], "3.9 8.6 0.9": ["urinate"], "-1.7 12.8 4.9": ["deporting"], "-3.2 0.1 4.8": ["busses"], "-2.0 0.4 6.9": ["awardees"], "7.7 3.1 1.1": ["turnstiles"], "18.3 3.0 6.6": ["plazas"], "-0.6 6.0 8.5": ["hungrier"], "-3.3 -0.4 19.7": ["weeknight"], "0.2 17.7 11.2": ["rationality"], "15.5 10.2 12.9": ["wiggle"], "-2.0 -2.8 7.0": ["overpayments"], "11.6 8.5 21.7": ["catamaran"], "9.7 10.7 5.0": ["brawls"], "-1.0 15.1 6.2": ["dispossessed"], "10.6 13.1 19.9": ["twigs"], "13.8 9.7 5.1": ["nigh"], "10.1 10.9 7.0": ["newlywed"], "17.6 18.0 8.1": ["oligarchs"], "12.2 2.3 0.3": ["thinnest"], "18.3 6.6 -7.3": ["divesting"], "14.1 16.1 7.6": ["spits"], "5.4 13.2 9.3": ["firmness"], "10.6 2.2 21.0": ["carvings"], "2.0 8.5 1.3": ["sunroof"], "9.0 28.4 0.7": ["paratrooper"], "-4.6 1.2 4.0": ["obstetrician"], "1.3 6.2 20.9": ["gout"], "-10.2 0.7 3.5": ["pianists"], "3.4 4.8 6.0": ["heightens"], "3.0 7.9 10.9": ["restock"], "6.6 7.4 33.0": ["smelt"], "19.6 5.0 6.7": ["transfixed"], "4.1 5.1 3.9": ["inkjet"], "6.3 -3.7 16.8": ["cookery"], "18.2 9.0 7.3": ["yawn"], "-0.6 7.4 9.2": ["seedings"], "1.8 2.4 6.3": ["realizations"], "8.7 8.6 38.4": ["succulent"], "2.9 6.8 14.1": ["snowboarder"], "3.7 17.9 7.4": ["stubbornness"], "-0.4 15.9 -9.2": ["undivided"], "13.8 1.7 13.3": ["scaffold"], "-4.6 3.6 2.1": ["republished"], "8.1 -0.9 1.2": ["childrens"], "5.8 10.3 12.8": ["ecologist"], "8.6 4.9 2.6": ["elasticity"], "1.3 10.7 4.6": ["assent"], "0.9 3.8 18.0": ["boarders"], "17.1 17.0 11.5": ["midair"], "0.6 13.9 -1.8": ["glorify"], "-5.0 6.9 -2.4": ["articulation"], "10.4 19.9 3.1": ["cowed"], "6.7 16.6 5.9": ["spectral"], "-1.3 15.7 4.4": ["echelon"], "-0.0 7.2 -1.4": ["ventilated"], "3.6 9.8 4.9": ["defusing", "bequeath"], "-2.9 8.0 8.1": ["overdo"], "10.3 1.9 3.6": ["embossed"], "1.4 7.8 1.5": ["regretting"], "1.7 5.9 -2.3": ["encrypt"], "7.0 3.2 9.8": ["prosthetics"], "11.0 10.6 11.5": ["crucifix"], "-6.2 12.1 14.4": ["aquifers"], "12.9 -2.8 -0.2": ["predates"], "-5.2 9.3 4.9": ["tiebreakers"], "3.0 3.9 4.5": ["comparability"], "6.8 -0.8 3.9": ["mi"], "6.1 10.4 6.0": ["imperil"], "3.8 16.9 2.6": ["wedded"], "2.0 6.8 13.3": ["firecracker"], "-2.3 9.6 11.9": ["sacrament"], "11.0 4.7 25.7": ["platters"], "-3.9 -1.6 -9.3": ["commends"], "9.9 4.8 3.8": ["exploitative"], "0.3 8.7 7.0": ["afflicts"], "4.8 4.0 2.0": ["depositary"], "24.9 -0.3 11.7": ["swirls"], "8.9 7.7 9.2": ["stoplight"], "-2.3 11.0 24.9": ["wintertime"], "4.4 15.2 9.7": ["overland"], "-4.5 27.8 6.5": ["intel"], "-12.1 -3.5 13.8": ["heifers"], "0.9 6.1 -0.1": ["endeared"], "3.0 10.4 14.2": ["emo"], "-2.1 3.1 -0.5": ["getter"], "2.5 12.8 18.1": ["shallower"], "-4.9 8.5 -1.8": ["aspirant"], "1.3 6.2 11.6": ["characteristically"], "4.7 0.1 -1.7": ["workmanlike"], "3.1 8.3 5.7": ["amalgam"], "16.7 6.8 15.2": ["lawnmower"], "5.5 18.3 2.2": ["theocracy"], "4.2 14.1 7.7": ["stereotyping"], "7.0 15.1 5.8": ["schoolmates"], "-3.4 4.7 4.1": ["medalists"], "-7.0 21.5 0.0": ["insubordination"], "3.7 13.2 2.3": ["cagey"], "0.9 1.4 2.4": ["refinements"], "-2.7 -0.6 3.1": ["enrolls"], "7.3 14.9 6.6": ["singularly"], "-5.2 8.7 3.8": ["summation"], "5.5 5.1 1.2": ["plied"], "7.0 11.8 3.8": ["raze"], "4.8 4.6 28.9": ["raspberries"], "-3.6 13.9 4.5": ["determinant"], "11.4 6.3 9.9": ["scamper"], "-0.2 4.9 -5.3": ["correctness"], "7.5 15.1 10.0": ["muffled"], "9.4 1.0 8.3": ["ebullient"], "12.1 21.3 6.3": ["swat"], "17.3 6.1 4.9": ["snaking"], "6.2 7.2 25.1": ["teal"], "2.9 12.9 13.0": ["birthright"], "-0.4 12.1 9.5": ["farmlands"], "1.1 16.8 0.9": ["hyperinflation"], "2.2 6.3 -5.8": ["exonerate"], "6.2 5.2 11.2": ["knobs"], "19.8 11.1 12.4": ["masts"], "5.8 11.1 4.0": ["unhindered"], "6.0 3.4 -0.6": ["preloaded"], "32.0 12.9 39.9": ["snail"], "-6.0 3.8 -4.5": ["confirmations"], "9.1 13.8 5.2": ["numbing"], "-1.3 3.8 2.6": ["serials"], "5.4 24.7 10.5": ["militarism"], "8.1 9.6 14.8": ["pivots"], "12.3 -0.7 12.1": ["fastened"], "5.3 8.8 2.1": ["muggy"], "10.7 13.5 7.3": ["foibles"], "1.8 7.5 3.4": ["falsification"], "8.2 3.3 5.4": ["aggregators"], "-1.4 9.0 -1.3": ["repudiated"], "6.4 11.7 23.0": ["monarchs"], "17.3 25.5 4.5": ["zealots"], "-2.7 20.9 12.2": ["blindside"], "4.8 16.2 11.3": ["pandemics"], "0.1 5.1 33.2": ["lentils"], "18.4 6.1 -4.5": ["disused"], "-2.7 5.0 3.0": ["augmentation"], "0.2 11.7 3.7": ["blurted"], "2.8 14.8 11.5": ["trenching"], "11.3 9.4 6.3": ["ails"], "7.9 4.6 6.5": ["aerosol"], "6.7 8.4 -2.1": ["unobtrusive"], "11.0 5.1 12.0": ["heath"], "1.7 21.7 8.0": ["conceit"], "2.7 15.8 0.2": ["involuntarily"], "1.4 20.2 7.1": ["extremities"], "8.6 16.0 6.4": ["cakewalk"], "0.5 1.8 3.9": ["regent"], "1.0 0.1 -0.8": ["timescale"], "13.9 8.6 62.5": ["clam"], "10.1 0.4 10.1": ["contented"], "13.1 0.7 9.6": ["pittance"], "-1.8 20.2 19.4": ["humanely"], "3.9 10.0 3.2": ["surgically"], "1.2 15.4 14.4": ["stagflation"], "3.8 7.6 2.7": ["wrested"], "-9.5 14.9 6.1": ["returners"], "5.8 -0.1 3.8": ["perusing"], "10.6 2.1 3.7": ["lug"], "4.4 10.9 7.2": ["inverse"], "13.3 17.1 2.7": ["trample"], "3.9 6.0 13.0": ["yellows"], "10.0 3.2 38.9": ["truffle"], "17.6 7.3 11.5": ["spines"], "6.2 10.7 8.4": ["dithering"], "3.7 11.0 9.0": ["panicky"], "-15.5 3.6 12.4": ["homebuyer"], "-3.4 8.5 0.2": ["imparting"], "9.0 1.3 13.8": ["backend"], "7.4 4.1 18.7": ["tickle"], "0.3 9.4 -0.5": ["airbag"], "-5.3 1.8 6.3": ["drownings"], "4.9 3.5 6.2": ["wanes"], "5.8 13.4 6.4": ["seeps"], "12.4 1.1 7.6": ["glossary"], "-2.1 17.0 6.2": ["admonition"], "8.4 5.0 1.5": ["deodorant"], "20.7 27.1 9.5": ["camouflaged"], "9.6 13.4 3.0": ["destabilized"], "-7.0 8.4 6.7": ["keying"], "18.2 7.0 7.8": ["lifelike"], "11.2 13.4 9.2": ["uglier"], "0.9 20.5 1.4": ["pushover"], "6.1 4.0 -1.3": ["debunk"], "2.7 5.7 1.6": ["bequeathed"], "17.1 12.9 9.7": ["voodoo"], "17.2 15.5 10.4": ["lander"], "15.6 5.5 15.2": ["sleigh"], "3.5 1.5 6.7": ["trashy"], "16.1 2.1 2.7": ["lugging"], "3.3 5.2 1.9": ["forbade"], "16.8 6.7 13.7": ["troughs"], "9.4 8.9 6.2": ["dissecting"], "-2.9 10.9 2.0": ["extricated"], "10.9 13.6 9.3": ["hinterland", "pantograph"], "-3.8 8.6 -0.6": ["liaisons"], "20.0 0.6 13.2": ["tubular"], "0.6 10.4 0.9": ["isolates"], "2.9 24.7 15.5": ["interceptors"], "-1.6 6.1 10.8": ["retry"], "1.6 5.4 3.1": ["implore"], "1.3 4.8 16.4": ["dieters"], "4.7 14.1 0.2": ["irreparable"], "-5.1 4.7 5.5": ["anesthesiologist"], "6.8 15.6 15.0": ["cyclones"], "0.1 9.7 11.7": ["taekwondo"], "3.6 12.9 9.1": ["disturbingly"], "9.8 5.0 11.4": ["hookers"], "-3.4 13.9 6.9": ["electrode"], "4.4 11.1 5.2": ["hilt"], "-1.9 13.5 -1.2": ["speechwriter"], "8.2 5.2 10.8": ["frat"], "9.1 8.5 4.8": ["restatements"], "11.6 21.8 0.5": ["vigilantes"], "5.4 14.9 4.1": ["incline"], "0.9 18.5 2.2": ["rightwing"], "13.6 6.0 14.3": ["nosed"], "9.0 8.3 23.2": ["beachgoers"], "14.7 14.9 8.7": ["backdrops"], "25.9 9.3 17.8": ["heaving"], "15.8 18.6 8.2": ["ravaging"], "13.8 14.3 5.1": ["dumbest"], "9.2 13.5 0.3": ["recapitalize"], "0.1 11.3 8.1": ["unfavorably"], "8.0 -0.8 1.9": ["lettered"], "-0.2 6.5 4.5": ["overshot"], "8.3 -1.0 1.1": ["sqm"], "4.1 5.5 9.5": ["anatomical", "viewerships"], "13.1 25.0 1.9": ["invades"], "9.3 9.1 12.8": ["tunneling"], "8.4 3.2 2.9": ["whiplash"], "10.4 7.4 6.9": ["arching"], "-11.5 2.8 7.8": ["outerwear"], "4.3 11.5 7.6": ["purest"], "-3.0 13.7 1.9": ["insufficiently"], "2.4 11.2 26.8": ["roosters"], "6.8 1.5 3.4": ["pique", "smartpen"], "4.7 2.2 8.1": ["chalet"], "-3.6 1.1 7.2": ["orchestration"], "3.0 10.0 14.9": ["ransoms"], "6.3 -1.2 14.6": ["lipid"], "1.6 14.1 3.4": ["bleeds"], "8.1 9.2 28.6": ["custard"], "3.3 4.9 2.9": ["disquiet"], "8.6 9.0 9.3": ["adware"], "-9.2 -3.4 5.3": ["issuances"], "1.2 8.2 6.3": ["partitions"], "1.9 36.7 5.2": ["insurgencies"], "5.6 9.0 12.1": ["ulcer"], "12.6 11.3 9.4": ["misfits"], "3.0 12.5 18.7": ["nectar"], "2.6 14.1 3.9": ["sacrosanct"], "-2.1 12.7 3.7": ["erring"], "7.7 12.1 9.9": ["fancies"], "-1.2 5.7 2.3": ["inclusiveness"], "5.3 11.1 15.7": ["weld"], "6.5 2.5 5.3": ["bristles"], "1.4 3.9 3.2": ["microns", "paravirtualized"], "5.7 14.0 12.1": ["resetting"], "7.8 10.3 2.8": ["misfortunes"], "15.1 11.8 10.9": ["melding"], "4.7 15.6 12.7": ["breaths"], "4.7 1.4 6.0": ["triglycerides"], "-2.7 7.4 2.3": ["retrace"], "6.4 13.1 5.0": ["semantics"], "2.4 12.3 9.4": ["bridesmaid"], "5.9 24.3 7.3": ["bigots"], "15.8 9.1 7.8": ["barreling"], "10.5 1.7 11.1": ["crystalline"], "-9.7 5.9 15.9": ["spay"], "8.1 2.7 2.1": ["unspectacular"], "15.7 21.6 26.0": ["caterpillars"], "-3.0 7.9 8.8": ["vaccinating"], "2.7 0.5 3.6": ["sociological"], "-3.5 -6.5 3.0": ["ext"], "21.6 0.7 13.8": ["crimped"], "0.5 -0.3 15.7": ["smelters"], "10.1 5.7 8.2": ["reshuffled"], "-1.0 16.1 0.6": ["propagated"], "1.9 16.2 7.1": ["taboos"], "-0.2 12.5 20.5": ["cockfighting"], "16.4 0.5 10.3": ["clogs"], "6.0 17.0 14.8": ["exclaims"], "6.3 18.9 4.4": ["pinpointing"], "-4.0 4.1 -2.6": ["troubleshoot"], "18.9 3.2 17.2": ["sunflowers"], "-13.3 -1.6 10.7": ["biennium"], "5.0 7.0 6.0": ["omitting"], "-2.3 15.4 13.2": ["takeoffs"], "-2.2 4.9 9.4": ["vii"], "2.2 6.2 -1.4": ["indiscretions"], "2.4 -5.1 0.3": ["resubmit"], "2.2 5.6 4.4": ["chicane"], "2.8 28.7 1.1": ["neutralizing"], "3.7 0.1 9.5": ["ovals"], "1.9 6.1 15.1": ["refrigerate"], "8.0 6.4 12.0": ["bridegroom"], "8.0 9.0 8.7": ["subculture"], "-1.6 7.6 7.5": ["sentimentality"], "9.3 1.3 4.6": ["typo"], "-0.9 4.8 11.6": ["transponders"], "-10.0 7.0 10.6": ["predeceased"], "7.5 1.8 -3.1": ["cements"], "5.2 4.6 6.1": ["bemoaning"], "-4.2 -0.3 8.0": ["homebound"], "9.4 16.9 7.0": ["parachutes"], "-5.1 0.9 12.9": ["alimony"], "-13.0 1.0 10.9": ["vintages"], "5.4 9.8 5.9": ["misbehaving"], "-1.5 13.6 3.7": ["parry"], "4.8 6.4 7.2": ["copes"], "28.1 4.7 2.6": ["superstore"], "13.7 2.1 -1.0": ["beckoned"], "5.2 18.1 6.8": ["cynically"], "-3.7 23.1 -0.6": ["atheism"], "7.3 18.8 10.2": ["coolness"], "5.4 15.1 8.9": ["plural"], "7.3 8.5 12.3": ["sloping"], "1.5 10.1 6.5": ["disenchantment"], "0.4 5.1 28.1": ["hummus"], "-13.3 6.8 6.3": ["jurists"], "-1.3 1.1 -0.6": ["wheelbase"], "-6.9 2.9 0.7": ["expunged"], "2.4 15.4 6.4": ["unjustifiable"], "8.5 10.7 21.0": ["pigments"], "2.9 10.6 1.1": ["disincentive"], "8.6 -2.2 3.5": ["milked"], "7.8 2.1 7.2": ["tinkered"], "7.0 1.8 7.4": ["dents"], "-0.6 3.6 7.3": ["fibula"], "7.3 27.7 0.6": ["fanaticism"], "7.0 0.7 9.9": ["playhouse"], "22.8 34.9 7.0": ["malevolent"], "14.4 8.1 12.0": ["awning"], "-0.1 2.1 12.6": ["towners"], "-8.0 -7.4 0.2": ["adjudicated"], "5.4 6.8 12.2": ["etching", "steamships"], "5.5 -4.9 10.0": ["totes"], "10.4 6.9 1.6": ["colluded"], "6.9 11.5 2.2": ["mistreating"], "17.3 6.8 8.6": ["pylon"], "-0.8 0.4 4.6": ["revisits"], "-0.2 12.1 6.6": ["annoys"], "1.9 12.2 7.7": ["enlists"], "6.6 8.4 13.9": ["dissection"], "1.3 4.2 6.5": ["laureate"], "6.8 9.9 7.3": ["cavalier"], "-3.6 4.3 2.6": ["flexibly"], "9.9 2.5 5.4": ["spunky"], "9.5 7.7 26.5": ["emerald"], "3.5 26.0 -1.6": ["malign"], "-1.0 8.6 -10.3": ["defamed"], "-0.4 14.1 5.9": ["divulging"], "13.5 3.5 2.1": ["renderings"], "4.0 9.4 11.0": ["girly"], "-0.3 10.2 5.5": ["vulgarity"], "12.4 -6.2 -1.5": ["strutted"], "-3.3 13.2 5.3": ["pander"], "6.5 -3.0 7.2": ["nutritionists"], "14.6 8.9 8.0": ["mannequins"], "7.7 10.4 4.5": ["condensation"], "10.0 11.6 5.4": ["proliferating"], "0.9 8.9 -4.0": ["absolve"], "2.3 11.3 1.7": ["cooperates"], "-4.8 17.3 1.9": ["telegram"], "-4.3 7.7 10.7": ["byelection"], "12.2 6.7 4.2": ["tightrope"], "0.1 1.2 -1.6": ["reusing"], "7.7 6.9 0.4": ["flaunting"], "1.2 12.2 2.5": ["deriving"], "-6.2 11.7 -1.0": ["stigmatized"], "-0.4 -0.8 2.1": ["effusive"], "7.6 12.6 13.5": ["comically"], "2.3 15.0 0.1": ["adamantly"], "-1.5 13.1 12.5": ["seamers"], "5.2 -1.8 7.3": ["url"], "9.7 6.1 6.2": ["heatwave"], "2.3 6.3 9.5": ["fashionistas"], "0.0 8.1 46.1": ["redfish"], "5.8 2.9 0.3": ["psi"], "-0.5 23.7 5.2": ["twos"], "7.2 10.9 3.7": ["erratically"], "2.1 -5.7 13.0": ["pageants"], "10.6 15.1 3.2": ["cog"], "11.8 14.2 7.5": ["harmlessly"], "10.1 2.7 7.4": ["fo"], "3.3 6.9 2.7": ["lulled"], "7.6 11.8 2.6": ["vapors"], "2.8 9.3 5.3": ["piston"], "10.0 8.1 0.4": ["underpants"], "11.3 10.5 28.0": ["cheeseburger"], "17.7 7.0 5.7": ["maelstrom"], "14.0 9.0 17.0": ["spirals"], "-0.9 9.4 6.5": ["newsman"], "-0.9 18.4 -3.8": ["falsehoods"], "-1.3 3.2 8.5": ["caching"], "-0.8 -5.7 5.4": ["graduations"], "2.7 19.3 -0.6": ["apologists"], "-0.3 18.6 -1.1": ["peacemaker"], "11.7 21.1 11.6": ["imprecise"], "8.6 16.4 20.8": ["feral"], "-4.8 21.4 6.0": ["confidante"], "2.6 4.7 8.1": ["crystallized"], "5.1 11.7 11.5": ["decal"], "11.0 22.0 10.9": ["loathing"], "-10.9 6.2 18.3": ["snowmobiling"], "2.6 3.7 10.0": ["scuffling"], "-0.2 3.1 3.6": ["scuffles"], "-5.6 4.5 2.8": ["elaboration"], "3.4 7.4 -2.8": ["repose"], "11.9 6.2 8.5": ["outfitting"], "2.0 4.2 9.6": ["multiracial"], "-1.3 5.2 9.6": ["naturalization"], "10.3 -2.2 7.0": ["clamored"], "4.4 10.2 3.3": ["endangerment"], "0.1 -0.2 1.6": ["garners"], "-3.3 13.6 -1.9": ["repudiate"], "-7.9 23.4 6.9": ["desertion"], "4.4 8.0 1.9": ["blurb"], "10.0 3.2 10.6": ["empties"], "13.3 0.9 10.4": ["floundered"], "15.0 11.3 11.6": ["coaster"], "12.4 8.6 12.3": ["punks"], "12.7 7.1 9.8": ["sculptural"], "7.8 20.1 0.1": ["demonizing"], "3.1 2.8 26.0": ["marinated"], "-5.0 2.0 -6.3": ["secs"], "8.3 10.0 1.3": ["entrench"], "3.3 7.0 4.9": ["bagpipes"], "13.0 5.8 4.9": ["shored"], "3.8 9.2 -0.6": ["inductee"], "-3.3 6.5 -4.5": ["induct"], "11.1 18.1 11.9": ["eternally"], "-1.4 3.9 7.6": ["transgendered"], "-2.6 0.0 9.7": ["selenium"], "-6.7 5.4 5.2": ["mastectomy"], "-0.2 15.3 2.0": ["outspent"], "6.5 5.8 3.2": ["zeroes"], "18.6 1.3 6.4": ["boxy"], "1.5 11.3 3.8": ["reticence"], "25.2 6.5 14.2": ["wobbling"], "8.5 6.7 18.6": ["pungent"], "1.1 11.7 11.6": ["craftsman"], "-3.3 -2.8 5.4": ["subbing"], "-1.3 6.8 26.4": ["cassava"], "1.0 11.1 6.1": ["traceable"], "1.7 10.7 10.3": ["supermajority"], "8.4 -5.2 13.8": ["beaded"], "7.3 -0.5 -0.6": ["loaning"], "18.1 20.1 31.1": ["slime"], "8.0 -1.0 5.0": ["accruals"], "7.7 2.5 -0.2": ["inducements"], "4.1 1.9 7.8": ["incubators"], "13.1 10.6 11.2": ["precipitous"], "3.1 27.1 0.1": ["seeker"], "4.0 10.1 12.1": ["carport"], "7.5 5.4 1.3": ["gurney"], "2.0 4.7 3.5": ["necessitating"], "0.2 -1.0 2.5": ["notation"], "-5.1 1.7 11.9": ["childless"], "1.3 7.3 -1.7": ["functionally"], "0.3 1.9 1.1": ["toning"], "7.5 12.7 7.5": ["tingling"], "3.9 10.5 8.3": ["legislating"], "17.3 7.5 11.0": ["twirling"], "-8.7 -1.8 10.7": ["juried"], "4.4 6.4 8.7": ["consenting"], "5.4 8.0 11.0": ["abbey"], "7.8 2.4 4.3": ["burnish"], "2.5 4.7 7.4": ["squalor"], "8.0 0.3 7.8": ["dapper"], "9.8 10.4 7.1": ["groan"], "-7.9 7.0 6.8": ["apoptosis"], "3.7 0.3 0.1": ["wattage"], "3.8 14.6 4.3": ["distorts"], "-2.0 14.5 5.1": ["misunderstand"], "17.0 14.9 9.2": ["cartoonish"], "6.3 24.9 3.7": ["grievous"], "4.5 3.5 9.0": ["powders"], "1.9 9.4 12.8": ["underemployed"], "3.4 12.9 13.4": ["fermented"], "2.5 0.3 9.1": ["keepsake"], "22.6 5.5 36.7": ["goldfish"], "19.3 22.4 5.2": ["nameless"], "-0.0 6.8 8.8": ["overloading"], "-13.0 9.1 2.6": ["candidacies"], "13.9 0.8 0.7": ["inking"], "3.0 9.5 9.0": ["subcommittees"], "14.8 15.1 12.0": ["darned"], "5.5 8.2 3.4": ["sellouts"], "20.0 -1.2 4.5": ["churns"], "5.9 13.5 0.4": ["obsolescence"], "14.3 7.6 0.9": ["hyping"], "4.3 8.4 6.9": ["contrition"], "4.2 2.1 15.2": ["aground"], "6.7 3.5 1.4": ["downplays"], "4.8 4.3 10.8": ["silica"], "-11.2 8.7 4.3": ["novelists"], "-1.7 -3.5 -1.1": ["stillborn"], "5.9 4.1 5.5": ["manhole"], "-1.1 2.6 5.1": ["nanomaterials"], "7.0 6.5 8.2": ["sleaze"], "-10.7 11.4 -0.6": ["speakerphone"], "10.8 16.0 5.7": ["outmoded"], "8.0 12.5 3.2": ["popularly"], "15.3 8.8 5.5": ["microwaves"], "7.1 1.2 2.9": ["relocations"], "2.4 21.9 1.4": ["repulsed"], "9.0 3.4 0.6": ["aced"], "6.7 5.8 11.7": ["medicare"], "2.3 12.5 5.6": ["categorization"], "3.7 12.0 11.0": ["blueline"], "21.8 4.8 7.0": ["incongruous"], "7.0 17.2 12.3": ["redrawing"], "8.9 11.7 13.4": ["artfully"], "8.8 13.4 20.1": ["pebbles"], "0.9 3.1 6.7": ["contrite"], "4.2 24.7 2.4": ["outgunned"], "-0.6 32.0 9.3": ["squadrons"], "2.5 14.9 8.9": ["fester"], "13.7 2.1 15.9": ["multistate"], "5.3 12.1 7.3": ["adrenalin"], "5.2 -1.4 3.6": ["toughening"], "-5.5 15.6 2.3": ["defensible"], "0.3 7.8 8.4": ["paternal"], "0.3 2.9 2.9": ["gasification"], "2.5 7.6 5.1": ["nabbing"], "0.6 15.4 4.8": ["defaulters"], "8.3 9.6 15.7": ["lunacy"], "7.7 4.2 8.4": ["tradeshow"], "-0.8 9.2 12.7": ["meditative"], "-6.3 12.3 5.9": ["tradeoff"], "8.3 8.3 10.0": ["libido"], "3.9 4.6 3.8": ["carjacked"], "6.4 8.6 8.1": ["nanotubes"], "8.0 2.0 13.5": ["mummies"], "8.1 11.1 4.5": ["bloodletting"], "22.0 7.9 29.2": ["goo"], "7.4 10.2 7.1": ["dew"], "-4.6 3.2 6.3": ["feedstocks"], "9.1 9.3 -7.4": ["imminently"], "20.2 2.8 12.3": ["dangle"], "3.3 17.6 0.9": ["alleyway"], "0.5 0.2 4.1": ["appreciably"], "0.3 4.0 -1.4": ["psychotherapist"], "4.5 8.4 6.9": ["patently"], "13.5 -7.2 3.8": ["finalizes"], "1.2 -1.8 6.8": ["supersede"], "-3.4 5.6 0.0": ["permissive"], "10.2 18.3 4.8": ["counterfeiters"], "4.3 11.0 7.8": ["roadsides"], "6.1 -4.3 4.4": ["signup"], "12.4 11.6 14.2": ["blackboard"], "2.4 -2.4 4.4": ["revue"], "-8.4 13.0 0.7": ["perceptive"], "3.6 10.2 0.4": ["impermissible"], "5.9 10.9 10.1": ["throwers"], "3.4 10.2 7.5": ["bewilderment"], "17.3 11.4 13.3": ["rusting"], "6.5 17.2 1.2": ["repellent"], "9.5 15.7 3.3": ["disguising"], "6.6 3.3 3.1": ["giggled"], "-2.6 7.7 -1.2": ["hemorrhage"], "3.1 4.6 5.5": ["vomited"], "4.3 10.0 3.3": ["megapixels"], "8.3 12.7 9.5": ["irrelevance"], "11.6 10.4 8.0": ["curving"], "5.0 6.6 2.4": ["aesthetically"], "10.7 29.0 5.4": ["villainous"], "4.5 4.3 15.1": ["preservative"], "1.1 10.6 8.3": ["agrarian"], "5.1 6.6 19.9": ["thawed"], "4.1 18.0 14.5": ["replenishing"], "3.8 38.5 7.8": ["treachery"], "2.8 16.3 6.8": ["unpalatable"], "2.0 6.3 1.0": ["infusing"], "-0.8 16.1 3.8": ["meditate"], "-4.3 15.8 8.9": ["philosophically"], "-1.0 -2.0 10.7": ["organics"], "6.8 8.5 -4.1": ["syncing"], "4.8 12.8 8.8": ["sullen"], "2.6 5.7 9.6": ["sleepover"], "5.4 8.3 9.1": ["repainted"], "8.0 10.3 5.7": ["inorganic"], "1.0 11.6 6.3": ["conventionally"], "4.7 10.9 9.2": ["pushy"], "6.9 -0.7 7.8": ["limousines"], "5.5 12.2 5.3": ["squirm"], "11.3 -3.0 -5.5": ["peddled"], "-0.3 -2.6 10.9": ["swimsuits"], "17.5 -0.6 8.2": ["topper"], "1.2 14.2 9.7": ["backstory"], "1.0 2.9 8.2": ["wardrobes"], "7.8 9.0 10.3": ["torpedoed"], "2.3 7.0 3.7": ["bandmate"], "-4.5 13.6 3.3": ["necessitates"], "6.2 14.6 13.8": ["northernmost"], "-5.4 1.0 6.8": ["viola"], "-4.1 18.5 -0.4": ["denigrate"], "8.8 8.2 9.3": ["celluloid"], "13.5 11.4 13.1": ["gloriously"], "12.2 6.4 34.0": ["pelicans"], "16.3 4.5 8.1": ["walloped"], "11.7 9.7 4.6": ["jogger"], "2.6 5.7 -2.4": ["plat"], "6.5 -0.4 7.6": ["dishwashers"], "-0.8 11.4 3.1": ["outwardly", "physiologically"], "9.2 15.9 12.9": ["forearms"], "-1.5 17.2 0.0": ["denunciation"], "18.4 3.7 10.1": ["dealmaking"], "21.7 9.1 5.0": ["cubicles"], "-6.7 14.2 -1.2": ["alertness"], "12.0 6.3 6.5": ["snug"], "16.1 6.3 6.7": ["copious"], "-0.4 7.8 5.4": ["sensuality"], "-0.2 5.9 -1.2": ["litigate"], "4.2 10.9 5.3": ["supercar"], "4.7 10.8 5.8": ["jetliners"], "1.5 22.6 5.0": ["beatable"], "4.3 11.7 15.9": ["eyelids"], "-0.9 8.6 6.1": ["contemplative"], "6.5 15.1 16.8": ["brat"], "6.9 18.7 2.8": ["paradoxically"], "-3.8 15.4 27.9": ["salinity"], "2.3 11.5 10.8": ["leprosy"], "8.9 4.8 11.8": ["meadows"], "9.2 8.1 6.5": ["minutiae"], "2.9 4.4 5.9": ["sexting"], "5.7 17.2 -0.3": ["emir"], "13.8 14.5 3.5": ["ruinous"], "0.7 -2.5 0.3": ["pored"], "10.1 14.0 2.9": ["obsessively"], "6.2 7.7 11.0": ["haulage"], "7.9 2.7 7.9": ["knickers"], "-5.7 9.3 6.8": ["oncologists"], "9.2 3.8 4.2": ["quadriplegic"], "1.6 8.6 11.4": ["masturbation"], "3.7 6.1 7.2": ["unpretentious"], "3.3 11.4 5.9": ["trilateral"], "9.4 8.5 18.4": ["excavator"], "18.5 15.3 11.9": ["insides"], "0.5 0.7 -5.9": ["cassettes"], "13.5 2.0 6.8": ["octogenarian"], "11.5 26.5 20.7": ["termites"], "-6.0 21.6 0.3": ["defame"], "8.0 2.3 14.8": ["incubation", "louisiana"], "13.8 9.5 0.7": ["cobwebs"], "-2.9 8.0 24.8": ["marinade"], "1.4 19.5 5.4": ["transgression"], "14.0 14.3 5.4": ["hottie"], "11.7 6.2 17.5": ["boatload"], "-7.3 5.5 6.1": ["directorial"], "6.0 -3.3 0.7": ["trialled"], "-3.5 5.2 1.6": ["technocrats"], "6.3 3.5 -0.2": ["hounding"], "6.4 6.1 10.8": ["earmarking"], "8.2 3.8 9.5": ["baring"], "11.2 0.2 -2.8": ["digitize"], "4.4 1.7 7.8": ["proffered"], "-2.4 1.7 5.4": ["karting"], "20.4 -1.3 6.5": ["souped"], "-0.4 5.4 6.7": ["nines"], "7.7 4.4 4.7": ["monochrome"], "1.6 8.4 9.7": ["circumvented"], "8.7 2.9 9.2": ["ers"], "5.7 7.0 0.3": ["configuring"], "1.3 -6.0 13.4": ["ang"], "-2.5 4.2 -0.4": ["ophthalmology"], "-3.5 8.6 12.3": ["theatergoers"], "4.7 10.7 9.3": ["vetoing"], "6.8 15.0 22.9": ["chow"], "-2.2 8.5 6.0": ["intervenes"], "11.0 10.0 27.2": ["feasts"], "0.6 -0.3 32.7": ["mozzarella"], "-6.6 3.7 2.9": ["vaginal"], "7.2 11.2 12.8": ["windstorm"], "15.4 4.1 10.8": ["oddities"], "1.3 -4.8 20.5": ["gilt"], "-4.2 8.1 7.6": ["biopsies"], "14.4 18.7 10.0": ["talisman"], "-4.1 8.1 8.4": ["skippered"], "12.2 14.0 8.8": ["screenshot"], "-3.2 7.9 9.0": ["surmise"], "-4.1 1.1 6.3": ["dropoff"], "5.3 21.7 4.8": ["befriend"], "9.9 6.3 3.2": ["aeronautics"], "-0.5 2.5 3.3": ["sedative"], "9.7 7.5 3.7": ["vuvuzelas"], "0.0 -2.9 5.8": ["incontinence"], "8.1 -1.0 13.6": ["genteel"], "5.5 1.7 1.1": ["weaning"], "12.7 -1.9 11.5": ["uk"], "3.6 11.4 4.5": ["tidbit"], "9.2 1.1 10.3": ["ni"], "-6.9 6.8 0.6": ["hydrated"], "2.4 10.5 7.3": ["impersonator"], "0.8 13.5 11.7": ["axles"], "13.0 6.6 7.6": ["throttled"], "-0.6 9.0 6.7": ["nourished"], "1.2 11.7 5.9": ["predisposed"], "0.8 18.4 6.3": ["instigator"], "-2.5 16.5 25.0": ["dispersants"], "-3.1 14.1 11.4": ["linemates"], "-8.8 8.0 10.5": ["postpaid"], "6.9 4.7 12.8": ["hobbyists"], "1.3 2.7 64.7": ["grouper"], "6.0 3.0 14.8": ["hipsters"], "16.7 5.4 21.7": ["ivy"], "17.5 2.8 13.6": ["clockwork"], "3.1 13.3 8.7": ["amputees"], "8.7 7.6 4.2": ["outran"], "8.5 16.0 8.1": ["abject"], "7.9 7.7 2.0": ["connotations"], "-9.1 17.1 5.9": ["divisiveness"], "2.7 5.5 11.2": ["smelting"], "10.1 4.7 5.3": ["scooted"], "7.3 -0.4 27.4": ["tortilla"], "-1.7 15.5 4.4": ["disengaged"], "17.9 11.5 22.8": ["ostrich"], "1.1 12.8 8.2": ["materialistic"], "8.7 8.7 7.3": ["misnomer"], "4.7 17.8 10.5": ["onlooker"], "10.0 19.0 0.1": ["telegraph"], "-8.9 5.8 4.6": ["relatable"], "9.4 13.5 8.3": ["itchy"], "5.6 11.8 12.9": ["entomologist"], "-0.0 -2.0 14.4": ["colocation"], "4.8 7.3 11.0": ["preservationists"], "-2.0 8.8 1.1": ["pleadings"], "-13.5 2.5 6.3": ["probationary"], "-5.6 3.7 5.9": ["concerto"], "12.0 8.8 16.7": ["chipmakers"], "1.0 15.7 12.7": ["authoritarianism"], "6.5 7.4 3.4": ["decently"], "7.2 -2.5 3.8": ["weaned"], "-3.8 8.7 5.8": ["femininity"], "-5.0 5.5 10.1": ["fluctuates"], "9.5 6.7 1.9": ["ingestion"], "0.1 6.8 7.1": ["congenial"], "-2.0 6.1 -3.7": ["appellants"], "-4.1 5.5 12.7": ["dressings"], "-0.9 4.3 14.2": ["probiotics"], "6.2 10.4 11.5": ["softens"], "10.7 11.5 18.0": ["chokes"], "21.5 14.2 11.9": ["gulp"], "24.3 0.5 12.5": ["plopped"], "3.5 5.2 2.0": ["lighters"], "21.8 8.6 9.5": ["stupendous"], "7.2 9.7 5.2": ["lectern"], "-3.1 11.8 10.5": ["improvisational"], "11.3 6.9 5.3": ["postman"], "5.9 4.0 9.4": ["sequenced"], "15.5 7.2 8.4": ["weirdest"], "3.1 4.7 9.0": ["bemoan"], "2.7 14.4 5.3": ["commandments"], "0.6 10.7 26.8": ["seasonings"], "1.0 11.9 7.9": ["recriminations"], "-0.3 11.6 10.6": ["hypotheses"], "5.6 15.8 10.9": ["counterintuitive"], "12.9 10.1 22.7": ["paddles"], "13.8 6.9 8.1": ["menorah"], "-0.1 8.1 18.1": ["methamphetamines"], "6.1 12.1 -2.0": ["unsung"], "7.6 12.0 4.5": ["exhale"], "3.3 8.5 18.1": ["grating"], "0.3 0.6 0.6": ["attests"], "6.5 6.0 8.0": ["quickened"], "18.5 5.2 5.9": ["swindle"], "7.7 3.1 8.0": ["seepage"], "6.4 16.7 7.9": ["inalienable"], "5.6 8.2 10.7": ["magma"], "4.3 15.7 6.6": ["monotony"], "9.8 26.1 9.0": ["asymmetrical"], "13.5 23.3 13.2": ["moles"], "-3.2 14.9 4.5": ["reestablish"], "6.3 18.4 -4.8": ["avowed"], "4.0 7.2 -4.9": ["subsection"], "9.0 17.2 4.2": ["smokescreen"], "-6.9 -5.6 3.0": ["recaps"], "1.9 6.8 4.0": ["inscriptions"], "12.5 14.9 11.3": ["buster"], "-4.1 0.3 -3.5": ["sensitize"], "7.3 3.0 0.9": ["clots"], "-1.9 7.9 5.4": ["premised"], "7.2 1.0 8.6": ["hyperlinked"], "-5.4 -2.8 4.6": ["kbps"], "-4.9 5.1 9.1": ["roadwork"], "5.0 14.8 4.3": ["unreachable"], "3.3 0.3 5.3": ["fillers"], "12.6 8.9 9.6": ["blissful"], "15.4 3.6 5.1": ["delighting"], "5.8 0.5 8.7": ["underlie"], "8.7 4.1 4.2": ["surfed"], "9.9 10.0 14.9": ["mime"], "5.3 -1.5 2.8": ["adopters"], "-8.0 5.2 3.4": ["catheters"], "-5.4 7.4 1.6": ["accommodative"], "15.2 11.7 15.9": ["puffs"], "6.8 5.0 8.1": ["undercuts"], "1.2 45.3 15.1": ["combatant"], "18.4 3.9 11.2": ["thon"], "11.1 -9.7 -1.1": ["bilked"], "7.1 17.8 -0.5": ["corrupting"], "12.2 8.7 9.2": ["assemblage"], "14.5 2.1 2.7": ["wheezing"], "3.3 5.4 3.2": ["unleaded"], "18.6 7.5 10.2": ["hobble"], "-2.0 17.0 8.2": ["disobeying"], "4.5 2.2 5.8": ["si"], "-2.6 7.7 7.9": ["nonsmokers"], "13.4 7.4 17.1": ["yanking"], "5.4 6.2 12.2": ["highlands"], "-11.7 11.2 5.6": ["antiviral"], "-1.5 15.3 7.0": ["disturbs"], "6.4 2.1 -1.6": ["fainting"], "16.4 13.1 3.9": ["american"], "12.3 8.1 6.7": ["hotshot", "digibox"], "-3.3 5.4 -8.6": ["spokespersons"], "2.2 10.4 5.5": ["inadequately"], "-0.5 3.7 7.1": ["avg"], "9.6 2.3 13.1": ["denser"], "5.0 1.3 1.8": ["mens"], "2.9 4.8 10.1": ["hilarity"], "9.6 0.7 -4.2": ["und"], "16.7 1.0 1.7": ["gracing"], "3.0 7.6 0.4": ["tryst"], "-5.7 1.5 1.5": ["turnouts"], "10.5 -1.6 9.8": ["oomph"], "12.3 3.0 12.4": ["polyurethane"], "12.4 20.2 27.6": ["spears"], "6.8 4.9 5.4": ["reroute"], "5.4 8.6 0.7": ["razing"], "9.4 11.5 8.4": ["suction"], "10.4 8.6 12.4": ["hardcourt"], "3.9 9.6 8.4": ["actuary"], "6.4 -1.7 15.0": ["aprons"], "5.4 8.3 15.2": ["jeou"], "7.1 -0.8 10.5": ["liven"], "9.5 12.3 14.0": ["misty"], "7.1 -3.4 3.7": ["stg"], "12.5 4.1 6.6": ["shilling"], "5.8 18.3 7.7": ["myopic"], "2.2 18.8 11.3": ["photons"], "5.5 -4.6 6.1": ["sewed"], "-0.6 10.2 -1.4": ["suspenseful"], "18.0 12.2 6.3": ["superimposed"], "-0.6 3.1 22.8": ["hams"], "8.0 8.7 6.6": ["deathbed"], "-4.0 -0.3 10.7": ["violins"], "3.4 1.0 13.8": ["mascara"], "-4.3 17.3 5.2": ["dissension"], "-1.8 26.5 -1.8": ["informer"], "7.7 19.3 2.0": ["unlocks"], "9.2 10.5 -1.9": ["emanate"], "8.6 11.1 5.8": ["negating"], "7.2 13.0 13.0": ["speedboat"], "8.2 17.0 5.7": ["miscalculated"], "8.9 8.2 2.2": ["pronouncing"], "6.2 2.2 0.8": ["resuscitated"], "-2.1 8.8 0.5": ["disconnection"], "23.3 10.7 5.6": ["genie"], "11.2 10.2 9.5": ["symmetrical"], "9.4 12.8 7.4": ["gasps"], "1.7 1.4 5.6": ["reforestation"], "9.8 10.1 3.7": ["blockaded"], "-1.8 8.1 0.7": ["nominates"], "-1.4 -5.0 4.6": ["intakes"], "17.3 1.6 11.4": ["chucked"], "6.9 7.5 6.7": ["proudest"], "5.4 16.1 10.6": ["subtleties"], "0.8 19.4 5.3": ["brotherly"], "12.8 23.5 2.0": ["inhospitable"], "7.5 3.3 14.3": ["panning"], "-1.1 9.3 6.9": ["blemishes"], "-8.9 -2.6 0.7": ["ophthalmic"], "20.1 13.3 7.1": ["utopia"], "9.0 4.7 56.8": ["crawfish"], "7.6 13.9 2.4": ["republics"], "5.6 -2.3 -1.6": ["rehearing"], "5.4 8.2 10.1": ["wallow"], "4.8 0.6 1.0": ["cedis"], "12.9 5.3 5.7": ["underlies"], "4.2 17.4 5.6": ["affray"], "10.7 12.1 25.3": ["avian"], "14.8 11.3 7.0": ["oxymoron"], "10.3 18.5 11.1": ["merciful"], "18.6 13.4 8.5": ["wingspan"], "-0.5 6.7 11.5": ["goalmouth"], "8.2 6.3 11.3": ["fasteners"], "4.7 7.4 12.1": ["bailiff"], "19.5 32.0 6.5": ["crusaders"], "-3.5 -0.7 -1.4": ["affordably"], "7.1 7.7 5.9": ["postmodern"], "-11.7 1.7 -2.0": ["psychosocial"], "-3.8 23.1 1.5": ["honorably"], "3.0 11.5 5.9": ["kickboxing"], "3.5 1.1 11.2": ["haulers"], "6.6 -2.8 9.5": ["tony"], "3.5 6.5 1.4": ["stretchered"], "10.3 19.5 6.5": ["valiantly"], "11.5 1.1 4.4": ["gaunt"], "1.2 15.1 4.2": ["sorrows"], "10.0 26.0 7.8": ["mutants"], "-1.5 7.7 10.4": ["mountaineering"], "11.2 6.8 16.5": ["terrier"], "-0.8 0.8 -6.8": ["commending"], "15.6 10.4 7.7": ["nooks"], "6.6 8.8 7.9": ["calms"], "2.6 14.8 1.6": ["combatting"], "-9.6 7.0 3.9": ["interment"], "3.0 11.2 7.8": ["virgins"], "4.1 3.2 5.1": ["peeved"], "5.6 14.4 12.9": ["cocked"], "6.2 14.1 9.4": ["consciences"], "2.7 11.3 8.8": ["hes"], "6.0 2.1 0.1": ["res"], "9.0 3.9 1.0": ["amateurish"], "9.2 18.0 7.7": ["nebulous"], "14.6 17.1 3.6": ["accelerometer"], "1.4 17.4 34.4": ["manatees"], "9.5 2.5 9.1": ["casings"], "-5.2 4.1 -1.2": ["litigated"], "-1.2 7.5 0.0": ["desiring"], "14.8 9.1 2.3": ["dethroned"], "12.9 7.0 40.6": ["noodle"], "6.7 25.4 20.7": ["decoys"], "1.4 0.8 3.9": ["medians"], "-6.0 1.9 8.3": ["judgeship"], "0.1 6.6 0.2": ["broadcasted"], "4.7 11.9 4.9": ["oddsmakers"], "2.1 15.2 6.3": ["befall"], "4.5 7.2 5.4": ["sociable"], "0.1 29.0 0.7": ["falsehood"], "3.4 -1.2 2.8": ["footbridge"], "-8.9 1.6 7.5": ["reconvened"], "7.5 11.1 8.9": ["rationed"], "-4.5 4.3 0.8": ["monotherapy"], "21.7 6.5 27.9": ["gooey"], "10.7 12.2 1.5": ["irrevocably"], "11.5 9.9 6.4": ["circumventing"], "7.4 2.2 6.7": ["transsexual"], "1.9 6.3 -2.3": ["expeditious"], "16.8 2.3 16.7": ["girth"], "1.3 8.4 6.9": ["shah"], "3.4 4.4 5.9": ["policed"], "15.3 4.6 7.3": ["sfr"], "-1.7 17.7 7.7": ["paraphrase"], "9.9 3.8 6.7": ["glimmers"], "12.8 2.1 19.9": ["doggie"], "0.5 11.2 1.8": ["flirty"], "4.4 -0.5 4.5": ["shorn"], "8.5 16.8 8.5": ["revolting"], "10.2 2.6 4.7": ["beeline"], "4.3 8.9 12.8": ["patios"], "17.5 21.5 6.9": ["noxious"], "14.1 4.7 10.3": ["stub"], "16.1 0.5 13.7": ["wrinkled"], "3.3 16.8 7.7": ["nostrils"], "14.2 8.2 -2.5": ["repositioned"], "6.2 -4.5 5.0": ["collages"], "4.6 3.6 4.1": ["rankled"], "3.1 15.2 11.6": ["groundstrokes"], "-2.8 18.2 6.3": ["holiness"], "-1.5 -1.3 4.6": ["disburse"], "9.4 -0.8 3.4": ["expensed"], "13.2 10.1 1.4": ["shiver"], "-4.5 2.1 10.8": ["sweatshirts"], "-5.8 0.7 3.7": ["curtailment"], "9.8 1.4 11.0": ["jugs"], "3.8 11.2 7.1": ["unionization"], "4.5 5.1 7.3": ["compendium"], "-1.4 19.8 5.1": ["immorality"], "7.8 7.6 15.6": ["grate"], "5.7 12.0 13.6": ["brawling"], "-3.0 2.7 11.7": ["bodywork"], "8.6 7.6 1.7": ["astrology"], "9.6 13.2 7.9": ["slasher"], "8.5 14.7 3.6": ["torturous"], "4.8 -3.4 3.4": ["mixers"], "5.8 5.8 8.2": ["mournful"], "2.8 19.0 4.0": ["justly"], "-3.3 -0.1 -3.0": ["liaising", "sedqa"], "1.9 2.7 5.0": ["safekeeping"], "5.1 14.9 10.9": ["procrastination"], "25.6 -3.3 7.1": ["snazzy"], "8.8 15.1 4.9": ["beacons"], "8.1 30.7 4.5": ["fascists"], "7.1 5.1 15.5": ["smoothie"], "4.6 6.4 8.1": ["inimitable"], "20.4 10.9 10.3": ["glows"], "1.2 5.8 4.3": ["freelancer"], "6.8 14.9 13.4": ["spade"], "-1.0 4.0 4.8": ["addendum"], "1.1 23.1 -4.8": ["perpetrate"], "18.8 8.4 6.4": ["throbbing"], "7.1 8.4 0.7": ["addressable"], "12.7 0.4 2.9": ["svelte"], "0.9 5.5 0.6": ["consumable"], "-9.9 11.5 -8.5": ["oaths"], "-2.0 11.1 16.0": ["fertilize"], "-0.5 3.5 10.6": ["immaturity"], "8.8 11.9 8.3": ["magnify"], "8.7 -2.1 5.5": ["piggyback", "typeset"], "9.0 12.8 9.1": ["wailed"], "-1.5 8.8 11.4": ["headlight"], "10.9 7.2 -3.3": ["infotainment"], "4.5 -8.4 4.8": ["sted"], "10.6 -2.8 6.3": ["hubbub"], "9.7 7.8 7.8": ["hemmed"], "9.4 2.8 3.7": ["crematorium"], "1.7 8.6 10.8": ["acerbic"], "0.8 13.8 -1.7": ["differentiator"], "-0.5 9.9 4.3": ["interrelated"], "7.1 4.3 7.4": ["airtight"], "27.1 6.6 12.5": ["garish"], "22.5 4.8 9.8": ["kiddie"], "6.0 17.6 7.6": ["surest"], "7.5 2.8 5.9": ["coattails"], "2.9 9.5 7.7": ["screener"], "11.5 4.1 19.0": ["mashed"], "15.4 -1.2 5.0": ["sparkled"], "3.5 16.3 -1.4": ["professes"], "1.2 8.9 5.5": ["transpire"], "-0.3 10.6 10.2": ["traditionalist"], "-0.4 7.0 14.3": ["midwicket"], "18.1 -9.3 6.5": ["forked"], "5.8 7.9 6.3": ["leveler"], "8.4 13.7 1.5": ["revolts"], "22.3 13.8 8.5": ["flinging"], "3.8 4.6 10.9": ["twang"], "-0.4 7.6 14.2": ["headlock"], "-1.2 11.7 -5.6": ["truthfulness"], "-8.4 6.3 6.1": ["motorcycling"], "9.6 5.3 12.2": ["jumbled"], "16.3 3.9 23.7": ["gingerbread"], "14.5 -1.1 14.5": ["glittery"], "-3.4 11.7 4.8": ["sandbagging"], "-2.7 4.9 9.6": ["portables"], "0.2 16.2 6.2": ["inhibitions"], "3.3 17.4 -9.1": ["depose"], "2.8 7.3 10.3": ["subsystem"], "1.2 -1.6 15.9": ["florists"], "-1.7 11.7 4.2": ["distracts"], "0.4 7.6 18.2": ["kiln"], "9.4 11.2 11.4": ["outta"], "-6.2 1.5 8.0": ["forties"], "2.2 11.9 0.0": ["assimilated"], "11.3 3.7 20.3": ["greyhound"], "13.8 15.2 4.8": ["everytime"], "16.2 14.5 9.5": ["disintegrating"], "7.3 16.3 11.0": ["growl"], "11.1 6.7 7.5": ["squelch"], "10.7 0.5 4.5": ["spotlighting"], "5.3 3.7 13.1": ["rackets"], "-5.2 8.2 5.9": ["emigrate"], "3.4 5.1 5.8": ["rashes"], "-3.1 3.4 -0.3": ["tarnishing"], "11.1 2.3 7.8": ["brightening"], "7.1 15.9 15.7": ["aristocracy"], "18.9 17.6 15.3": ["fairies"], "26.0 3.9 9.1": ["smallish"], "10.3 1.5 18.7": ["dollop"], "11.3 16.3 9.1": ["whatnot"], "12.4 4.5 11.4": ["animator"], "7.1 44.2 -2.1": ["infidel"], "24.0 8.4 30.3": ["peacock"], "4.2 5.1 6.5": ["chiseled"], "13.9 15.0 5.5": ["infatuation"], "-0.3 11.1 12.1": ["dialects"], "2.7 21.9 1.3": ["smears"], "5.0 4.0 6.0": ["penniless", "rasterizer"], "6.2 2.2 12.3": ["jailhouse"], "6.5 3.6 18.4": ["bayou"], "-2.1 3.7 -0.4": ["acceptability"], "-4.9 9.0 22.8": ["chardonnay"], "-5.9 11.6 3.1": ["hesitancy"], "6.7 1.6 8.4": ["ap"], "-4.7 2.9 4.8": ["codec"], "-4.1 8.3 4.6": ["captaining"], "5.3 11.8 5.9": ["proportionally"], "3.3 9.7 14.3": ["tungsten"], "10.6 15.6 4.7": ["paradoxical"], "3.9 9.8 4.0": ["extorting"], "-1.2 7.8 6.6": ["pruned"], "6.2 -2.8 3.9": ["vivacious"], "11.7 16.1 -4.6": ["bombarding"], "6.5 7.0 4.8": ["transitory"], "11.7 21.7 6.5": ["mythic"], "1.7 -6.3 7.2": ["chaperones"], "6.2 5.8 4.1": ["turntable"], "20.2 22.9 13.5": ["marauding"], "7.8 -6.5 7.8": ["raffled"], "10.5 13.6 6.1": ["huddling"], "1.7 12.6 3.6": ["sweethearts"], "29.8 15.3 20.1": ["puny"], "1.1 7.0 1.3": ["pip"], "0.8 7.2 4.2": ["brevity"], "3.0 3.4 -3.6": ["emanated"], "-3.4 -1.8 8.9": ["liturgical"], "3.3 9.1 35.8": ["chilli"], "11.8 2.1 2.0": ["popularize"], "16.2 20.0 5.2": ["amorphous"], "7.2 7.7 9.4": ["racecar"], "2.5 21.0 5.1": ["credo"], "2.8 6.3 0.3": ["memorialize"], "0.7 6.6 6.0": ["flyout"], "-1.0 8.1 12.8": ["heterosexuals"], "1.9 -0.8 7.5": ["saddles"], "12.9 11.7 12.4": ["junkyard"], "21.0 7.2 7.0": ["retractable"], "13.9 11.6 8.5": ["licked"], "7.0 6.4 -1.1": ["rejuvenating"], "-4.9 10.7 14.6": ["neutering"], "12.3 5.4 13.8": ["ware"], "14.6 5.6 -3.2": ["headquarter"], "0.8 -0.1 -3.0": ["guaranty"], "1.7 16.4 8.9": ["readjust"], "-8.1 2.9 3.5": ["subbed"], "13.1 4.9 4.5": ["collides"], "9.0 6.1 6.8": ["symphonic"], "-3.1 9.5 5.0": ["accede"], "6.6 19.8 5.8": ["recoil"], "1.9 3.1 12.2": ["sororities"], "3.2 1.2 10.3": ["supple"], "4.5 17.3 3.5": ["allusion"], "10.1 1.2 -1.0": ["quashing"], "13.1 15.3 7.2": ["taming"], "5.4 5.3 -0.8": ["liberalizing"], "6.6 4.2 6.2": ["rerouting"], "17.2 9.8 7.8": ["insatiable"], "13.8 8.7 24.3": ["nachos"], "11.9 3.4 17.7": ["domes"], "3.7 9.9 10.6": ["moaned"], "-1.6 13.4 40.0": ["pheasant"], "8.8 8.2 4.4": ["rans"], "14.2 7.4 5.3": ["upstage"], "8.5 9.5 6.5": ["imitated"], "13.6 24.8 9.9": ["badass"], "1.1 3.1 19.4": ["topsoil"], "-3.1 6.9 7.2": ["codified"], "2.1 17.7 8.0": ["demonstrably"], "1.4 7.4 -1.7": ["vindicate"], "1.8 15.5 4.4": ["senders"], "19.8 3.5 -1.8": ["companys"], "3.0 3.2 3.0": ["compiler"], "-4.6 2.8 -1.5": ["businesslike"], "-6.5 2.8 0.3": ["refresher"], "-4.7 3.6 7.8": ["triathlete"], "21.9 6.5 8.3": ["grandest"], "14.5 4.2 13.9": ["freebie"], "-0.5 8.4 9.6": ["infertile"], "6.7 13.7 11.8": ["summarily"], "-0.0 6.8 6.8": ["agonized"], "6.2 -0.9 17.2": ["boozy"], "12.5 12.6 2.2": ["energetically"], "1.4 1.0 8.2": ["karts"], "6.0 3.1 8.1": ["english"], "14.5 0.2 -2.3": ["dispensers"], "7.1 3.2 7.2": ["stiffened"], "25.4 2.4 6.8": ["upstarts"], "17.5 10.1 3.5": ["chaps"], "9.6 10.0 20.3": ["roulette"], "1.3 3.8 -0.6": ["womens"], "7.9 11.2 2.5": ["impracticable"], "5.4 15.1 12.4": ["photosynthesis"], "-7.1 -2.1 6.8": ["disbarred"], "7.4 10.4 14.0": ["pol"], "26.3 4.8 8.8": ["creaking"], "15.0 16.7 12.4": ["idiocy"], "3.1 9.3 5.4": ["subwoofer"], "8.4 13.9 12.4": ["precipitously"], "8.8 12.4 7.0": ["altruism"], "3.5 12.3 18.9": ["lifeboats"], "10.7 7.3 3.6": ["juxtaposed"], "5.2 7.2 2.2": ["exerts"], "9.9 0.8 -0.5": ["compressors"], "0.7 10.1 16.8": ["straits"], "-7.6 11.1 5.8": ["interjected"], "-3.2 2.9 9.4": ["epidemiological"], "1.7 8.7 0.3": ["reconnecting"], "2.5 8.3 3.4": ["spellers"], "4.7 -3.2 13.4": ["waxed"], "7.6 10.4 7.5": ["dugouts"], "7.0 8.0 4.6": ["pervades"], "-1.1 19.4 11.5": ["libertarians"], "-3.1 28.1 1.7": ["dishonor"], "8.2 7.2 -2.1": ["centralizing"], "8.4 17.0 2.7": ["invincibility"], "0.0 0.9 11.1": ["sash"], "16.0 -0.2 10.7": ["groovy"], "1.7 12.5 -2.5": ["disparage"], "-2.0 4.8 1.4": ["retried"], "14.5 6.4 6.6": ["helluva"], "2.2 12.2 4.6": ["sleepers"], "13.6 5.3 4.1": ["metamorphosis"], "13.4 6.1 12.3": ["fingertip"], "5.0 11.5 -5.9": ["publically"], "-10.4 -6.5 2.1": ["tenures"], "-1.8 10.9 8.9": ["judiciously"], "6.2 4.8 16.6": ["brownie"], "2.9 2.7 1.3": ["semiannual"], "9.4 10.0 11.7": ["unscientific"], "10.7 11.6 15.5": ["weirdness", "playa"], "5.4 -2.6 -0.1": ["terminates"], "2.1 13.8 10.2": ["wrecker"], "9.6 7.5 14.3": ["snarl"], "-2.3 2.3 16.9": ["moped"], "13.1 11.8 9.6": ["rovers"], "1.7 5.8 1.5": ["bookshop"], "-2.9 12.3 4.8": ["factually"], "13.8 8.3 19.9": ["kangaroos"], "-1.0 13.0 8.9": ["habitable"], "9.1 17.1 3.1": ["incalculable"], "7.7 19.3 2.2": ["propagating"], "7.1 1.3 17.9": ["bronzes"], "-3.5 6.3 12.6": ["pacers"], "13.6 8.2 6.6": ["prototypical"], "9.4 3.1 6.8": ["riyals"], "6.4 5.4 18.2": ["thumbnail"], "-2.8 5.3 6.9": ["adjuvant"], "13.4 9.6 19.5": ["violet"], "10.9 8.4 6.5": ["zenith"], "-5.2 8.2 0.7": ["ambiguities"], "13.6 6.4 9.5": ["yore"], "1.5 6.7 4.0": ["veers"], "2.9 14.8 1.1": ["beholder"], "5.4 7.5 8.5": ["petulant"], "5.0 13.6 9.0": ["cynic"], "4.0 17.8 5.4": ["unaccountable"], "12.3 3.2 7.2": ["juiced"], "-2.8 6.9 2.8": ["toolset"], "8.1 20.4 1.8": ["infallible"], "16.2 9.4 7.1": ["cradling"], "12.8 -2.3 4.7": ["perked"], "5.9 14.0 0.9": ["rouse"], "6.3 22.8 13.2": ["uppercut"], "16.8 4.0 13.9": ["tots"], "5.1 5.7 7.0": ["bottlers"], "3.1 4.3 1.6": ["journeyed", "presentationally"], "12.3 26.3 31.1": ["slugs"], "17.9 9.0 4.3": ["bristling"], "11.0 14.4 -0.1": ["dethrone"], "-6.8 1.2 14.5": ["feedlot"], "4.2 -1.9 12.2": ["lei"], "12.5 -2.2 3.9": ["basked"], "0.4 4.4 5.7": ["roadworks"], "-2.4 3.0 32.9": ["pecans"], "-1.9 10.1 23.3": ["phosphorous"], "12.0 15.7 0.4": ["unmistakably"], "6.6 12.0 15.3": ["hoe"], "7.3 5.7 3.4": ["permeate"], "-0.1 9.2 21.2": ["pollination"], "15.7 13.5 5.7": ["tricking"], "9.1 4.2 3.3": ["squalid"], "2.7 -5.6 1.8": ["overdosed"], "10.5 5.9 3.4": ["washroom"], "2.2 5.0 8.8": ["staining"], "5.5 3.8 19.3": ["foreshore"], "-4.7 2.0 16.9": ["sari"], "12.9 15.0 6.1": ["prying"], "10.0 2.6 5.2": ["bucolic"], "-4.3 3.2 2.3": ["warfarin"], "5.2 3.3 26.4": ["melons"], "13.0 8.9 7.8": ["minarets"], "-3.7 4.9 12.8": ["comebacker"], "8.0 13.2 13.6": ["coop"], "12.5 15.5 7.9": ["gleeful"], "12.2 17.7 10.1": ["growling"], "3.7 14.1 4.7": ["metaphysical"], "9.7 1.6 14.4": ["shingle"], "3.2 30.4 4.4": ["maim"], "3.0 19.2 9.0": ["depraved"], "11.9 -3.2 -3.4": ["trailblazer"], "-0.2 11.9 36.5": ["stripers"], "12.6 6.0 9.2": ["pneumatic"], "11.6 17.1 0.4": ["messiah"], "-3.5 15.5 9.1": ["taser"], "19.3 3.7 5.0": ["trumping"], "-7.2 7.6 21.6": ["annuals"], "4.5 5.4 28.2": ["avocados"], "14.6 13.0 3.8": ["shrieking"], "0.1 8.1 8.5": ["reverts"], "16.7 14.7 19.8": ["speck"], "-2.0 6.8 -3.0": ["enriches"], "2.3 0.8 13.1": ["hairdo"], "15.4 12.4 6.9": ["blanketing"], "25.2 3.7 8.8": ["pitchman"], "5.5 0.4 -2.6": ["irregularity"], "12.7 2.0 12.1": ["bails"], "6.2 17.2 9.1": ["wryly"], "-0.1 8.1 0.7": ["aorta"], "4.3 9.5 7.9": ["touchstone"], "11.3 9.0 26.4": ["waffle"], "20.8 16.3 8.0": ["swathes"], "-7.6 1.5 4.4": ["metformin"], "16.2 9.1 7.4": ["brooms"], "-6.0 4.4 3.6": ["disinfection"], "2.9 13.0 10.1": ["irritable"], "-3.3 11.4 17.9": ["temperate"], "9.1 20.9 6.0": ["disguises"], "-0.8 12.6 8.9": ["midterms"], "14.4 5.0 7.1": ["marveling"], "-0.6 6.9 3.2": ["cd"], "9.9 13.6 8.2": ["unaccustomed"], "11.4 11.6 7.9": ["drips"], "1.9 34.7 7.0": ["infiltrators"], "-4.8 9.4 2.1": ["observances"], "4.6 9.3 8.5": ["sleight"], "2.3 13.4 4.8": ["ultraviolet"], "7.4 2.5 14.8": ["artsy"], "6.9 6.2 17.3": ["enamel"], "2.6 20.4 20.7": ["strait"], "14.9 5.2 6.8": ["replicates"], "1.4 2.3 3.2": ["seamstress"], "5.5 9.1 5.7": ["obsessions"], "-6.1 2.1 6.0": ["getaways"], "2.7 -2.7 6.0": ["webcasting"], "5.1 4.1 10.5": ["tailing"], "12.2 4.8 4.6": ["convulsions"], "7.5 6.7 4.5": ["damping"], "0.4 14.3 1.3": ["annexing"], "13.8 8.3 2.0": ["unceremoniously"], "11.4 4.0 5.6": ["excitable"], "3.1 -1.8 3.6": ["lotions"], "12.1 8.2 7.1": ["riven"], "14.2 1.5 9.2": ["jigsaw"], "0.4 3.1 5.6": ["corpus", "microfluidic"], "8.5 6.0 1.0": ["overpay"], "2.3 7.5 10.5": ["excavate"], "9.5 -4.8 14.6": ["fetches"], "8.4 4.7 25.8": ["skimmers"], "-1.5 20.1 8.5": ["embittered"], "7.6 0.9 17.9": ["sampler"], "-0.4 -2.0 4.2": ["secretarial"], "3.5 5.0 7.3": ["grapevine"], "6.9 22.4 15.8": ["crewman"], "8.7 9.2 2.0": ["quelling"], "6.6 5.7 26.6": ["daffodils"], "8.6 17.3 2.6": ["appeasing"], "-0.9 8.2 -1.8": ["reactivated"], "-1.2 10.7 -1.4": ["condemnations"], "1.0 -6.9 3.4": ["refunding"], "-7.5 -1.4 11.5": ["triathlons"], "21.5 9.6 11.0": ["toaster"], "12.0 -2.1 6.0": ["scuppered"], "12.4 2.7 7.5": ["purgatory"], "4.5 4.2 18.7": ["sunsets"], "7.0 5.5 8.8": ["synthesizer", "dourest"], "-2.8 10.4 5.3": ["eliciting"], "5.7 3.8 7.0": ["disappointingly"], "-0.3 8.1 12.2": ["equitably"], "2.4 14.0 -0.1": ["overestimate"], "-3.6 14.0 -0.2": ["dispersion"], "-9.3 7.6 2.5": ["nett"], "3.7 11.5 7.7": ["decadence"], "6.9 7.5 13.9": ["whiffed"], "3.7 7.7 6.3": ["reactivate"], "2.2 3.6 17.1": ["thoroughbreds"], "10.1 8.1 20.7": ["stag"], "25.9 13.3 16.6": ["swallows"], "7.0 10.7 7.0": ["penance"], "-3.3 8.0 13.0": ["overeating"], "-1.5 19.8 2.7": ["belittle"], "-3.1 3.4 -4.8": ["incentivize"], "2.2 7.4 -6.3": ["indemnify"], "6.0 4.4 5.2": ["coverings"], "7.0 -5.4 9.7": ["tiara"], "16.0 7.6 5.2": ["reuters"], "5.0 1.0 3.4": ["dabble"], "11.5 24.3 14.1": ["samurai"], "-2.9 12.3 6.1": ["cuffed"], "2.7 16.8 12.1": ["conniving"], "10.6 19.9 6.5": ["illusory"], "8.4 20.2 9.4": ["botnets"], "12.7 9.2 9.7": ["hunky"], "-0.0 9.8 -3.9": ["deplore"], "26.0 10.8 7.0": ["wizardry"], "20.4 13.5 3.8": ["gizmos"], "2.6 4.7 -3.1": ["upgradation"], "-5.8 15.8 -1.7": ["traumas"], "11.9 14.6 19.4": ["mush"], "20.0 3.3 2.9": ["adorning"], "-0.3 4.9 3.1": ["sips"], "-0.9 12.5 6.4": ["glib"], "-8.1 13.1 8.5": ["prosecutorial"], "2.7 12.8 12.4": ["bullpens"], "8.0 7.3 9.4": ["knighthood"], "-2.1 2.0 8.1": ["kindergartens"], "-5.7 19.6 -0.3": ["rightist"], "-7.5 10.4 6.2": ["evidentiary"], "17.0 17.9 4.4": ["behead"], "0.9 0.5 9.2": ["telecommuting"], "5.1 2.6 9.7": ["bailiffs"], "13.7 15.7 26.7": ["beavers"], "4.4 -7.3 6.3": ["binders"], "3.6 3.2 10.1": ["cataract"], "-1.4 3.3 12.4": ["bluesy"], "-1.5 15.0 -0.5": ["gunbattles"], "11.0 5.5 10.4": ["regalia"], "6.0 10.2 7.1": ["maladies"], "2.0 5.5 19.2": ["fenders"], "-7.1 2.7 10.5": ["synod"], "4.9 6.7 9.6": ["wince"], "0.0 10.4 1.4": ["impurities"], "19.3 38.3 17.6": ["invader"], "-2.9 3.7 5.9": ["roadster"], "-6.4 9.0 17.2": ["forester"], "-2.1 2.2 8.8": ["naphtha"], "13.9 8.5 5.9": ["outback"], "7.8 4.7 11.3": ["jarred"], "3.5 15.5 6.3": ["masterfully"], "14.9 34.3 4.9": ["bloodthirsty"], "-0.8 21.3 11.0": ["opposites"], "8.6 19.6 11.6": ["malady"], "11.7 11.1 11.3": ["connoisseur"], "-2.1 6.8 8.3": ["metrology"], "8.1 13.0 13.7": ["ping"], "4.0 6.5 3.4": ["straightening"], "8.1 11.7 0.1": ["shellacking"], "1.9 1.1 9.8": ["meshed"], "15.2 8.0 1.0": ["afire"], "-8.2 2.8 5.3": ["educations"], "-1.5 3.2 8.5": ["consignments"], "9.0 15.5 0.8": ["doggedly"], "10.4 5.9 31.5": ["flaky"], "6.0 -0.8 13.4": ["lightened"], "-0.9 2.8 12.1": ["leaching"], "7.2 10.0 12.9": ["bookie"], "6.2 10.5 41.7": ["manatee"], "4.0 4.1 1.6": ["degeneration"], "20.0 9.3 17.3": ["triangles"], "12.6 11.5 14.3": ["sheepishly"], "-8.5 9.0 5.3": ["identifications"], "3.1 1.0 14.8": ["mittens"], "-6.0 7.5 4.0": ["commutation"], "7.1 1.3 5.9": ["topline"], "9.7 8.0 13.4": ["bile"], "8.0 -9.0 1.2": ["allayed"], "6.4 3.6 4.7": ["spats"], "5.0 5.2 5.4": ["linguistics", "zoophilia"], "-4.5 -1.1 -1.4": ["subscribes"], "-3.2 2.2 7.0": ["electives"], "13.7 12.1 28.9": ["maggots"], "14.1 12.5 7.4": ["helpfully"], "2.9 3.4 0.8": ["preyed"], "5.6 3.3 11.8": ["ka"], "-1.4 11.4 9.3": ["garda"], "1.6 9.9 6.6": ["forbearance"], "-2.8 -2.1 1.3": ["photocopy"], "6.5 11.5 14.9": ["engraving", "detuning"], "1.9 7.1 2.7": ["sixteenth"], "3.0 11.1 21.2": ["cougars"], "22.9 14.0 17.1": ["whacking"], "2.5 11.1 14.6": ["customarily"], "-1.0 14.0 7.9": ["acids"], "-4.9 7.8 9.5": ["opiates"], "0.8 2.5 4.4": ["forfeiting"], "6.3 6.2 -0.7": ["phenomenally"], "11.6 9.3 3.1": ["blistered"], "5.6 2.7 4.2": ["capitalizes"], "7.4 1.0 26.9": ["chewy"], "15.7 10.7 5.5": ["phalanx"], "-3.0 4.9 5.7": ["sportscaster"], "10.1 15.0 6.1": ["putative"], "-3.7 5.8 10.8": ["nitrate"], "1.5 8.0 -0.8": ["reassures"], "-0.9 4.2 5.1": ["evens"], "0.2 17.1 8.2": ["khaki"], "9.6 4.8 26.1": ["porridge"], "8.0 4.5 14.7": ["materializes"], "7.5 -1.1 34.4": ["cheddar"], "-3.0 15.6 7.6": ["electorates"], "8.7 12.7 -1.1": ["carcinogen"], "2.2 14.8 -2.3": ["credibly"], "-4.8 11.0 3.2": ["genital"], "14.1 9.7 6.4": ["stringing"], "14.3 31.7 14.1": ["stealthy"], "0.8 8.3 2.4": ["bookshelf"], "7.0 11.5 20.2": ["freighters"], "8.9 0.7 -0.6": ["printable"], "6.5 11.3 11.0": ["stunk"], "12.4 17.5 14.0": ["coworker"], "-2.7 0.2 11.6": ["isotope"], "3.2 -2.3 16.7": ["plaid"], "6.9 8.5 11.3": ["pining"], "2.4 7.9 2.6": ["hooliganism"], "6.7 2.2 16.9": ["rams"], "11.8 4.7 1.8": ["proliferated"], "-0.2 14.7 7.9": ["infirm"], "10.4 9.0 0.6": ["dupe"], "2.2 4.5 3.3": ["legroom"], "5.5 20.3 4.2": ["interdependent"], "-1.6 4.1 2.7": ["pontificate"], "-9.7 12.2 -2.2": ["misquoted"], "0.2 2.8 7.6": ["toner"], "17.0 10.4 5.8": ["whooping"], "5.4 8.5 5.4": ["rotational"], "20.8 7.4 -1.3": ["superstores"], "7.0 6.1 15.5": ["cabbies"], "3.3 9.2 8.1": ["zeroing"], "8.0 2.3 17.9": ["landscaper"], "3.0 -5.6 11.7": ["biweekly"], "16.5 5.0 10.2": ["fashioning"], "1.8 1.1 12.6": ["cashmere"], "-5.3 5.3 8.6": ["cervix"], "17.0 7.7 25.0": ["horseshoe"], "7.3 7.3 7.7": ["galling"], "-6.2 9.5 2.0": ["interviewees"], "-0.6 6.1 14.0": ["polyps"], "12.5 9.0 4.1": ["torrents"], "3.3 5.7 0.5": ["impregnated"], "11.3 8.2 3.4": ["homogeneous"], "12.3 8.7 10.8": ["interminable"], "-3.2 6.9 8.3": ["observational"], "8.1 -3.1 9.7": ["polyethylene"], "2.6 9.3 3.6": ["immerse"], "9.6 12.3 11.2": ["bonfires"], "2.1 7.3 25.3": ["kayakers"], "15.1 6.7 8.5": ["sluggishness"], "2.9 8.2 13.5": ["fertilized"], "10.4 1.5 6.1": ["roomful"], "23.5 5.1 9.8": ["circumference"], "3.1 -0.3 -1.4": ["augur"], "16.8 5.9 20.2": ["shrunken"], "-6.6 12.7 8.7": ["delineation"], "5.8 21.1 0.1": ["unambiguously"], "5.2 13.5 8.7": ["adores"], "5.6 0.8 19.4": ["sculptors"], "6.2 11.8 7.6": ["hurrying"], "8.6 17.1 19.2": ["dick"], "3.7 14.4 12.9": ["purist"], "6.5 14.7 13.4": ["thoughtless"], "57.8 18.0 15.9": ["colossus"], "16.3 10.6 7.3": ["oops"], "-6.5 7.9 4.6": ["reassignment"], "9.2 16.5 -0.7": ["parachuted"], "2.9 7.5 0.1": ["fav"], "11.8 -2.8 -5.6": ["extolled"], "-8.4 11.7 -0.6": ["cohesiveness"], "5.6 21.7 5.5": ["vectors"], "9.3 9.3 5.7": ["homogenous"], "4.6 4.5 21.2": ["epoxy"], "7.8 5.9 9.7": ["hyperlinks"], "0.2 18.8 3.9": ["exertion"], "10.5 7.5 12.8": ["cellulite"], "9.4 8.3 13.2": ["rearranging"], "23.9 1.2 7.3": ["impresario"], "13.3 1.6 8.0": ["prof"], "3.8 8.7 4.1": ["fawning"], "9.6 12.6 15.2": ["genus"], "10.6 15.8 5.7": ["mystic"], "-0.1 19.3 9.1": ["presumes"], "1.1 5.9 13.5": ["rowed"], "15.9 2.1 12.1": ["circuses"], "4.9 5.1 3.8": ["muddied"], "8.1 2.6 1.2": ["cushioning"], "-6.4 3.2 10.2": ["inns"], "-3.3 6.8 14.7": ["lithography"], "-4.2 6.5 15.3": ["stallions"], "9.0 7.4 20.2": ["ferrets"], "2.4 2.7 10.6": ["overruns"], "-1.2 4.6 -0.5": ["bestsellers"], "-2.5 9.7 1.4": ["causal", "indviduals"], "4.4 19.6 2.5": ["smearing"], "0.6 18.9 1.3": ["emissary"], "11.9 18.1 8.6": ["dens"], "3.6 -8.0 2.4": ["waives"], "3.6 5.5 26.0": ["casserole"], "5.6 2.9 4.6": ["periodical"], "16.6 28.2 6.6": ["dastardly"], "13.8 8.7 15.1": ["feasted"], "-4.6 5.1 4.7": ["rescinding"], "15.8 -2.0 4.7": ["soothed"], "4.0 10.7 34.0": ["grits"], "10.0 25.8 9.9": ["deadlier"], "-3.5 8.1 1.3": ["faxing"], "11.0 2.0 -3.4": ["sodomized"], "14.7 7.2 8.1": ["techies"], "14.7 18.3 12.4": ["yoke"], "25.5 22.3 34.2": ["critter"], "3.5 2.8 2.1": ["detergents"], "6.1 4.3 -0.1": ["wallpapers"], "6.9 10.8 8.6": ["lightness"], "6.1 13.0 16.3": ["refuges"], "6.5 11.2 7.3": ["neighborly"], "-0.5 16.7 3.1": ["encroachments"], "8.1 12.7 2.8": ["unplug"], "-3.2 1.7 16.5": ["bleaching"], "-0.4 13.6 -3.2": ["proselytizing"], "8.7 18.0 7.5": ["analogies"], "1.9 12.0 15.6": ["trendline"], "-0.8 3.3 4.4": ["atoned"], "0.0 10.0 1.3": ["errand"], "7.6 8.3 13.9": ["mucus"], "13.9 4.9 4.5": ["stowed"], "14.2 21.0 5.4": ["superhuman"], "-2.9 6.9 5.5": ["prescribes"], "13.4 6.3 13.8": ["sparkles"], "21.6 11.2 5.2": ["laggard"], "12.3 8.6 6.1": ["grimy"], "12.0 22.7 0.8": ["bombard"], "0.9 10.9 12.3": ["splitter"], "11.0 31.1 3.4": ["hater"], "3.2 4.4 12.7": ["racquet"], "-7.8 19.6 5.4": ["apprehending"], "2.5 8.1 0.2": ["benchmarked"], "11.6 15.3 5.5": ["ageless"], "3.2 1.0 8.8": ["baggy"], "1.7 6.6 -2.3": ["quietest"], "6.6 1.7 3.7": ["te"], "7.1 17.4 1.5": ["gravest"], "-4.5 23.5 7.6": ["aviators"], "0.6 9.0 12.1": ["foundries"], "-3.6 2.8 2.1": ["octane"], "10.0 4.0 5.6": ["z"], "8.8 29.5 4.6": ["obliterate"], "1.7 13.9 8.0": ["fiat"], "15.0 13.6 31.5": ["grub"], "6.7 -0.3 16.6": ["bale"], "4.9 4.5 6.1": ["chalking"], "-1.6 3.7 4.4": ["regressed"], "2.7 4.8 0.8": ["desirability"], "3.2 3.6 0.7": ["notary"], "-4.6 7.6 13.9": ["archeological"], "13.8 9.8 10.6": ["cutout"], "1.3 5.8 8.7": ["checklists"], "8.6 3.1 7.3": ["bygone"], "-4.6 11.1 3.5": ["ophthalmologist"], "8.5 2.9 7.7": ["faultless"], "13.9 17.8 9.9": ["intruding"], "6.4 17.4 5.6": ["frighteningly"], "6.0 9.8 4.5": ["gambles", "vzaar"], "10.4 5.0 3.4": ["knighted"], "2.5 13.6 11.2": ["mountaineers"], "5.9 12.9 4.5": ["idealized"], "-8.1 4.3 5.0": ["doubleheaders"], "6.0 25.9 7.4": ["asymmetric"], "13.5 0.8 9.3": ["grander"], "12.6 4.9 3.8": ["crisscrossed"], "2.7 8.6 3.0": ["burglarizing"], "-11.2 6.5 -8.3": ["misdiagnosed"], "3.1 20.2 0.2": ["foment"], "3.7 6.4 5.3": ["treks"], "-0.2 4.0 -0.1": ["collated"], "16.1 -5.3 7.8": ["bubbled"], "13.8 21.2 4.0": ["bastions"], "15.4 10.8 6.9": ["unstuck"], "22.9 3.9 3.8": ["bankrolling"], "5.5 13.0 1.9": ["berating"], "1.0 1.8 -3.0": ["unwound"], "11.1 32.1 7.1": ["turret"], "9.3 4.0 1.6": ["flunked"], "3.6 8.5 5.6": ["backlight"], "-5.7 27.7 5.6": ["survivability"], "2.1 2.9 5.7": ["irks"], "11.8 -4.5 3.3": ["teetered"], "22.7 16.5 16.0": ["freakin"], "2.2 12.7 7.4": ["doorbell"], "2.0 12.0 10.2": ["ribbing"], "20.0 16.7 10.4": ["archetypal"], "-0.0 0.9 -0.0": ["legislations"], "1.0 5.1 1.6": ["segregate"], "4.2 12.3 8.1": ["teases"], "10.8 1.9 9.5": ["au"], "9.0 4.8 5.3": ["gimmicky"], "13.1 -7.2 0.7": ["bilking"], "-0.1 3.2 16.1": ["saplings"], "-10.3 -1.3 2.4": ["fieldwork"], "13.7 -1.0 3.4": ["bulked"], "4.4 5.4 13.3": ["manor"], "9.7 12.8 7.4": ["tombstones"], "4.7 7.2 36.9": ["cauliflower"], "-4.7 10.8 21.5": ["snorkeling"], "0.0 20.1 3.7": ["sufferer"], "6.2 6.0 9.0": ["recliner"], "5.7 10.6 4.5": ["wail"], "4.6 11.3 0.9": ["protestations"], "8.3 18.8 8.2": ["maul"], "0.3 2.5 8.9": ["hippocampus"], "3.5 3.9 1.7": ["harmonizing"], "4.2 7.2 4.0": ["thirteenth"], "6.3 0.7 7.8": ["subcontract"], "-3.0 8.1 14.2": ["perishable"], "0.1 7.0 3.6": ["molest"], "11.9 1.5 18.4": ["tricycle"], "7.1 18.5 9.5": ["opportunists"], "1.2 11.3 3.7": ["overextended"], "14.0 5.7 4.8": ["interwoven"], "7.2 15.8 21.2": ["browns"], "20.2 13.7 18.9": ["crawls"], "12.4 9.2 12.6": ["wallowing"], "4.3 16.7 2.7": ["tornados"], "12.9 5.1 -3.9": ["toothbrushes"], "8.1 8.5 -1.0": ["ensconced"], "0.3 9.8 5.5": ["mistresses"], "-2.3 25.2 8.1": ["unconsciously"], "15.5 8.4 16.2": ["sawing"], "-6.4 8.6 2.5": ["dryness"], "4.1 3.4 14.9": ["pastels"], "3.4 -5.5 4.7": ["dinged"], "24.0 16.6 4.7": ["swatting"], "-1.0 10.6 6.6": ["incineration"], "-2.6 3.0 6.2": ["mumps"], "17.4 9.9 5.5": ["telltale"], "5.3 31.5 1.4": ["antagonists"], "7.4 15.0 8.1": ["outhouse"], "14.8 7.9 4.1": ["triumvirate"], "-1.6 6.3 0.9": ["mitochondria"], "9.8 9.1 8.6": ["chattering"], "4.9 7.0 8.4": ["griping"], "2.9 13.6 3.3": ["givers"], "-3.6 1.8 1.0": ["compilations"], "16.4 17.0 8.8": ["thrusts"], "5.6 4.2 -4.4": ["debutants"], "3.8 20.0 9.2": ["barks"], "13.1 21.0 9.9": ["ferociously"], "1.2 18.0 9.5": ["separatism"], "9.5 -1.1 -0.4": ["struts"], "17.3 12.5 4.1": ["haystack"], "18.6 25.9 18.9": ["brute"], "5.3 8.5 5.4": ["startlingly"], "9.6 14.2 8.2": ["gatekeeper"], "10.6 12.7 4.9": ["bloodless"], "4.9 7.9 5.5": ["obliges"], "24.2 3.6 16.7": ["cylindrical"], "17.2 5.9 54.5": ["eel"], "1.6 4.7 11.2": ["rockabilly"], "9.6 -2.5 -3.7": ["digitization"], "2.8 8.2 -1.4": ["memorialized"], "3.9 2.3 9.1": ["emirates"], "11.0 2.8 -0.8": ["overpaying"], "6.9 4.9 22.6": ["waffles"], "-5.5 8.0 5.7": ["pilgrimages"], "6.7 19.5 7.1": ["heretofore"], "12.9 10.5 23.8": ["nibbling"], "-5.0 8.7 4.4": ["diverge"], "2.1 7.4 0.8": ["encephalitis"], "13.9 7.3 4.5": ["glimpsed"], "7.4 6.9 10.3": ["squeamish"], "-0.6 17.0 8.6": ["tacitly"], "6.4 7.1 4.6": ["strolls"], "3.3 24.9 4.8": ["savagery"], "10.9 7.6 0.6": ["sleuths"], "-1.3 1.9 -2.8": ["salable"], "5.5 -2.2 -2.0": ["laud"], "1.5 5.7 2.0": ["likelier"], "-4.8 6.2 6.2": ["cirrhosis"], "5.0 2.0 5.2": ["webcams", "urostomy"], "5.6 9.3 9.1": ["wildness"], "2.6 3.5 8.3": ["quads"], "-0.1 5.7 18.1": ["martinis"], "-6.5 6.2 4.9": ["framers"], "1.2 6.3 7.5": ["referenda"], "8.2 6.1 2.1": ["escapades"], "-0.5 4.1 -6.1": ["rebutted"], "-1.6 22.0 8.7": ["aviator"], "9.8 3.6 16.8": ["speedskating"], "21.3 5.9 5.4": ["boardrooms"], "5.3 8.3 8.2": ["denote"], "1.9 5.7 14.7": ["bawdy"], "14.2 9.6 6.8": ["masquerade"], "8.0 5.3 2.4": ["steamrolled"], "10.8 5.1 8.7": ["drool"], "0.9 9.6 -0.8": ["arguable"], "5.8 12.6 5.1": ["toggle"], "-2.8 1.5 2.5": ["patronized"], "14.4 -3.1 9.7": ["coliseum"], "17.5 6.1 12.9": ["rainforests"], "0.7 2.6 1.6": ["zloty"], "12.1 8.6 4.4": ["overstatement"], "2.1 8.5 4.3": ["bandleader"], "18.0 18.2 16.2": ["mythological"], "0.2 14.3 2.7": ["revere"], "-7.0 5.3 5.0": ["overdrafts"], "-1.3 14.0 8.6": ["unionist"], "10.7 1.9 12.0": ["stockbrokers"], "9.0 20.3 10.0": ["thorns"], "7.1 4.3 14.4": ["slaughterhouses"], "6.0 4.0 17.8": ["lotto"], "9.0 9.8 7.6": ["changers"], "1.8 1.9 -0.4": ["natively"], "7.3 6.0 18.7": ["cutlery"], "2.5 15.4 4.5": ["mouthing"], "11.0 5.6 6.5": ["gapped"], "5.8 11.0 13.8": ["stepchildren"], "13.1 4.8 2.8": ["gradient"], "6.0 6.9 1.0": ["undoubted"], "-1.3 2.3 5.9": ["levity"], "7.4 10.3 14.1": ["herpes"], "5.9 2.5 -4.0": ["unearthing"], "4.6 3.9 5.2": ["tenements"], "1.0 4.4 11.3": ["climatologist"], "11.6 12.5 8.8": ["chasers"], "-12.2 -3.1 12.6": ["caseloads"], "0.6 2.5 2.3": ["positivity"], "14.4 6.4 12.2": ["slowness"], "-2.4 1.6 7.6": ["chaperone"], "7.9 12.2 3.4": ["penicillin"], "4.6 9.5 29.6": ["guacamole"], "7.1 -0.7 1.2": ["todays"], "6.0 9.5 3.7": ["forthwith"], "10.9 4.6 20.7": ["muffin"], "12.3 5.2 6.1": ["clouding"], "4.3 5.8 2.4": ["circulatory"], "11.4 3.5 -1.7": ["shuns"], "-1.8 10.0 13.5": ["eyelid"], "5.9 -0.2 9.4": ["sideswiped"], "-5.4 2.3 3.1": ["midlevel"], "0.1 3.5 2.3": ["thermostats"], "7.8 7.8 9.0": ["iphone"], "5.8 3.2 13.4": ["crypt"], "9.2 26.3 10.4": ["duels"], "-0.6 9.9 2.0": ["exclusives"], "1.4 9.9 17.7": ["flavoring"], "2.8 9.6 3.3": ["presumptuous"], "14.4 10.3 7.6": ["anarchic"], "8.1 7.3 3.3": ["misadventures"], "9.2 10.4 12.1": ["stabs"], "-3.1 13.1 4.1": ["piety"], "7.3 3.0 13.4": ["decorator"], "6.0 23.0 1.6": ["gunned"], "-8.6 1.3 13.1": ["foals"], "-0.6 3.9 5.6": ["yearned"], "0.5 2.9 6.9": ["harmonic"], "1.9 3.5 -0.3": ["exude"], "-9.9 8.2 6.7": ["hemophilia"], "-5.0 5.3 -0.2": ["percentile"], "10.2 16.2 11.5": ["overreach"], "1.4 2.1 6.3": ["tuners"], "4.3 2.2 9.8": ["matte"], "1.7 5.8 5.8": ["treaters"], "12.9 1.2 3.2": ["tawdry"], "10.6 4.0 -3.0": ["internationalization"], "10.5 6.3 6.2": ["loo"], "4.9 4.0 22.1": ["trawling"], "10.9 22.1 5.9": ["gloating"], "-0.4 -0.2 0.6": ["appraise"], "3.5 14.3 0.2": ["conductive"], "9.1 11.0 4.7": ["encroach"], "8.1 6.7 9.8": ["glazing"], "14.2 23.1 17.3": ["decimate"], "5.6 13.8 11.3": ["swampy"], "10.5 12.1 5.0": ["quadrant"], "3.8 8.1 19.8": ["derbies"], "0.4 8.7 1.3": ["enjoined"], "0.5 9.0 22.9": ["marrow"], "9.9 7.5 14.6": ["steeple"], "14.0 23.4 5.9": ["unbreakable"], "4.9 1.5 -2.1": ["slimmest"], "7.9 14.9 2.4": ["realigning"], "3.4 7.3 5.5": ["modernism"], "1.5 6.7 11.6": ["sprinkles"], "2.1 9.1 3.8": ["extinguishment"], "5.9 2.1 5.5": ["loaders"], "-0.2 -2.1 4.0": ["trended"], "5.2 7.7 14.2": ["spacewalkers"], "15.0 10.2 1.1": ["zapped"], "8.3 14.7 11.8": ["hearth"], "5.6 15.5 7.5": ["overwhelms"], "-1.7 5.0 -2.7": ["forgeries"], "-0.5 6.4 2.6": ["shortens"], "13.9 17.4 9.9": ["chameleon"], "31.1 9.0 1.5": ["barons"], "10.0 15.7 5.5": ["perpendicular"], "-5.2 2.7 2.4": ["prescriptive"], "11.2 6.1 4.7": ["outgrow"], "-1.1 8.0 4.7": ["transmittal"], "7.9 5.7 14.1": ["skateboards"], "-1.4 -0.3 -2.6": ["recieved"], "10.1 17.3 7.2": ["forebears"], "29.1 12.2 35.5": ["minnow"], "27.6 10.7 10.4": ["hollowed"], "-5.5 12.1 -0.1": ["efficacious"], "3.9 12.4 -0.5": ["personalizing"], "21.6 -0.7 8.7": ["stodgy"], "21.9 5.8 6.6": ["chugging"], "3.8 4.2 0.8": ["atleast"], "8.3 7.9 3.6": ["watchman"], "11.2 12.3 -1.1": ["outsold"], "0.1 8.5 10.8": ["antiquity"], "6.5 7.7 2.6": ["evaporating"], "15.3 11.7 9.7": ["crowed"], "-2.5 16.4 2.7": ["reciprocated"], "7.9 -4.7 10.9": ["polypropylene"], "16.6 20.2 15.3": ["burrow"], "-1.4 6.6 18.7": ["mushers"], "3.8 6.2 9.4": ["bytes"], "5.7 14.5 -0.6": ["cleansed"], "5.4 6.9 9.4": ["nonchalant"], "-4.1 8.1 0.1": ["diesels"], "-3.8 1.7 -2.8": ["devotional"], "10.2 11.8 13.8": ["crowbar"], "8.3 13.6 14.0": ["dreamer"], "11.4 11.1 3.3": ["cuddling"], "2.3 2.6 13.3": ["prosthesis"], "1.0 1.5 -0.0": ["jot"], "-2.5 9.0 16.7": ["hypervisor"], "17.9 16.6 23.7": ["toads"], "9.7 15.0 3.9": ["misfiring"], "6.7 0.9 22.8": ["lagoons"], "4.7 13.7 1.3": ["exhilaration"], "-5.5 5.4 -0.0": ["punctuality"], "-4.2 16.3 -0.8": ["interlocutors"], "22.0 -4.7 7.3": ["mart"], "25.8 3.0 31.6": ["silvery"], "17.0 9.9 13.7": ["stinky"], "3.7 12.0 6.1": ["coalesce"], "3.9 21.2 1.7": ["fatigues"], "-2.0 7.5 7.5": ["homeruns"], "11.3 11.9 25.1": ["antelope"], "21.7 12.6 2.4": ["nationalizing"], "-1.0 16.1 3.7": ["antigens"], "14.7 6.0 6.1": ["careening"], "2.2 14.6 7.3": ["interdependence"], "10.8 6.1 3.0": ["wringing"], "5.9 -0.3 0.6": ["drummed"], "15.0 11.4 8.5": ["headlong"], "14.2 3.2 9.7": ["funnyman"], "-5.7 15.4 17.6": ["groundball"], "8.4 5.5 3.5": ["scrips"], "-2.0 1.6 10.1": ["dietitian"], "18.0 7.1 2.3": ["lookalike"], "9.6 12.5 6.8": ["unappealing"], "-3.9 7.0 1.0": ["breastfeed"], "-1.1 4.3 -0.4": ["remembrances"], "12.5 6.7 22.6": ["willow"], "8.5 7.1 1.1": ["quench"], "11.2 6.0 10.1": ["punchline"], "7.9 6.7 2.6": ["mathematicians"], "5.2 3.8 0.3": ["ducts"], "-4.1 3.9 7.4": ["multihomer"], "-2.6 9.1 1.0": ["brownfield"], "-2.5 9.6 12.0": ["brook"], "7.7 4.2 12.2": ["nipple"], "-5.9 0.5 14.0": ["femur"], "-0.5 5.2 4.8": ["rulebook"], "7.1 7.5 -2.2": ["redefines"], "17.5 11.8 -0.6": ["striding"], "3.1 3.2 10.9": ["schooler"], "-6.1 16.3 4.6": ["airframe"], "-2.7 4.7 3.6": ["subdivided"], "-9.7 -6.4 -2.1": ["recitals"], "13.8 10.5 8.6": ["checker"], "0.0 9.6 15.4": ["streaky"], "5.7 22.2 5.4": ["subterfuge"], "5.0 18.0 5.2": ["cellmate"], "12.6 12.7 11.7": ["chalkboard"], "-0.2 -5.5 7.1": ["microelectronics"], "0.8 6.1 3.9": ["rebuilds"], "11.4 10.4 1.8": ["numeric"], "-1.6 3.1 3.2": ["dramatized"], "2.4 3.9 4.9": ["comings"], "17.5 8.8 10.9": ["improbably"], "15.0 -3.7 7.2": ["housewares"], "-5.0 12.0 2.5": ["misinterpretation"], "5.3 8.1 10.6": ["stubble"], "4.2 17.2 3.9": ["vantage"], "-5.4 13.3 14.2": ["solder"], "10.8 17.6 9.2": ["pretenders"], "1.4 19.9 1.2": ["secularists"], "4.5 3.6 -0.9": ["intersects"], "26.2 13.0 13.0": ["rectangle"], "15.1 10.3 8.4": ["goverment"], "23.5 4.2 18.0": ["hamster"], "-1.9 12.6 -2.6": ["dissuaded"], "23.4 23.4 18.3": ["trolls"], "16.3 3.2 9.6": ["queasy"], "34.7 20.6 22.0": ["blob"], "6.2 1.6 6.9": ["chuffed"], "2.9 26.5 2.5": ["violator"], "-0.7 11.5 4.6": ["correspondingly"], "3.2 1.7 6.9": ["grosses"], "20.0 6.7 9.8": ["creaky"], "1.5 4.8 12.0": ["uncut"], "10.8 7.1 12.2": ["boogie"], "5.3 10.7 15.3": ["countertops"], "-6.4 10.9 4.9": ["reportable"], "15.3 9.8 4.9": ["laggards"], "13.0 26.1 2.5": ["cowering"], "6.0 18.1 1.8": ["bullhorn"], "3.7 3.6 17.3": ["browned"], "1.8 -1.8 3.6": ["stipulating"], "5.0 1.8 7.4": ["gigawatts"], "3.0 11.2 1.9": ["afflict"], "13.0 9.4 11.7": ["slings"], "11.3 8.1 9.3": ["contour"], "-2.1 -1.9 7.5": ["blouses"], "14.4 7.4 17.4": ["isle"], "-3.7 12.3 1.8": ["enroute"], "-0.9 4.6 -3.7": ["availing"], "6.3 -2.1 8.8": ["effervescent"], "8.6 4.0 23.1": ["burritos"], "13.5 8.3 10.5": ["atlas"], "-8.1 5.9 4.5": ["oratory"], "15.4 7.2 1.8": ["marque"], "0.7 0.9 3.9": ["lowdown"], "-0.3 -2.7 0.7": ["hairdressers"], "-1.3 1.8 12.1": ["racehorses"], "12.6 5.4 9.5": ["arched"], "2.7 9.4 13.0": ["overpopulation"], "5.0 10.8 13.9": ["hamlets"], "11.6 5.3 1.3": ["outshine"], "2.7 9.6 22.6": ["dinghy"], "3.8 10.8 9.4": ["playtime"], "-0.9 3.5 10.6": ["swab"], "12.1 3.4 30.5": ["aquariums"], "-4.9 7.1 3.6": ["ebook"], "2.1 3.7 -1.6": ["renege"], "4.7 44.5 -2.4": ["mujahideen"], "20.9 24.9 11.1": ["maniac"], "13.5 8.2 20.6": ["jerky"], "11.0 -3.8 14.6": ["curly"], "14.6 22.1 11.2": ["immobile"], "2.4 3.6 7.8": ["scuffed"], "-0.3 6.6 10.6": ["cloths"], "16.1 7.8 20.1": ["flopping"], "2.1 4.7 8.9": ["ephedra"], "4.0 0.5 4.5": ["tiff"], "14.6 10.9 9.9": ["herding"], "13.0 17.0 14.9": ["everyman"], "16.1 7.6 2.2": ["beckoning"], "0.5 6.7 11.2": ["fastbreak"], "10.1 27.7 13.7": ["grunts"], "4.0 7.3 4.2": ["taxiway"], "-2.6 4.2 -2.7": ["attested"], "-5.4 7.4 1.9": ["niqab"], "12.1 1.0 11.6": ["overlays"], "0.6 4.8 7.9": ["unkempt"], "-2.5 -2.9 -0.2": ["bios"], "1.3 9.8 2.1": ["unquestionable"], "3.6 16.3 2.2": ["shirk"], "3.7 9.0 11.4": ["cuz"], "32.8 11.4 13.6": ["monstrosity"], "0.6 10.5 -1.6": ["walkover"], "8.3 0.8 4.4": ["manicured"], "-2.7 15.1 7.9": ["exacerbates"], "3.9 2.4 1.2": ["der"], "-1.6 2.7 3.7": ["promiscuity"], "10.9 42.6 7.0": ["oppressors"], "18.1 -3.2 4.4": ["swindling"], "-5.7 5.7 7.1": ["screenwriting"], "0.6 8.6 11.9": ["intramural"], "3.6 17.4 8.0": ["nastiness"], "-1.1 10.7 10.7": ["luckier"], "22.4 7.5 -0.9": ["repairman"], "13.5 5.2 -4.1": ["turbocharged"], "7.7 20.0 6.9": ["grimly"], "9.3 5.4 6.8": ["tenement"], "13.4 10.5 3.5": ["imploding"], "14.5 18.1 9.9": ["prankster"], "7.9 14.4 1.0": ["locates"], "6.9 -3.1 15.7": ["uni"], "-11.8 12.4 3.2": ["debriefing"], "12.4 15.8 2.1": ["epoch"], "13.1 2.8 7.0": ["portend"], "-3.8 9.6 22.0": ["cognac"], "9.7 19.6 5.6": ["lifesaver"], "3.2 5.0 7.5": ["numeracy"], "9.1 12.9 10.2": ["neophyte"], "1.3 19.0 7.2": ["rationalized"], "8.0 14.6 25.7": ["hulls"], "14.9 11.3 -0.1": ["vibrate"], "-2.4 8.0 8.7": ["sportswriters", "abaya"], "9.4 9.3 16.2": ["brats"], "0.7 3.3 12.2": ["chlamydia"], "0.1 16.4 10.0": ["handkerchief"], "8.5 5.5 5.6": ["scratchy"], "13.5 5.1 9.2": ["hydraulics"], "3.8 25.3 8.4": ["asshole"], "13.3 2.7 4.0": ["eclipses"], "-0.1 1.6 4.7": ["chronological"], "-5.4 1.1 7.6": ["miler"], "9.6 7.7 8.9": ["anachronistic"], "11.0 10.5 10.4": ["jumpy"], "4.1 17.6 0.5": ["hereafter"], "3.5 3.7 17.9": ["diced"], "-2.0 11.5 5.6": ["jirga"], "-8.9 5.0 7.4": ["programmatic"], "3.1 5.0 3.9": ["perfunctory"], "-4.0 2.3 -0.9": ["postmortem"], "10.0 13.3 7.2": ["blacksmith"], "-1.4 10.2 9.9": ["autoimmune"], "4.5 13.9 5.0": ["immeasurably"], "19.5 6.5 21.4": ["encrusted"], "7.2 5.9 16.7": ["blackberry"], "-6.4 1.6 2.7": ["authorship"], "10.3 8.9 18.2": ["heartily"], "9.8 2.7 3.0": ["dispenses"], "-2.3 -4.9 3.4": ["keynotes"], "8.3 0.8 -1.0": ["shepherding"], "23.9 9.8 4.7": ["enveloping"], "-2.5 6.9 -6.4": ["equips"], "-1.9 4.3 7.7": ["syntax"], "5.0 2.6 15.7": ["scotch"], "4.5 11.0 11.0": ["narcissism"], "12.1 2.9 3.7": ["bonkers"], "6.7 11.9 -2.3": ["vehement"], "0.6 21.5 -6.0": ["defector"], "1.8 23.4 6.1": ["dearest"], "16.7 1.1 13.8": ["floppy"], "5.6 14.0 6.1": ["imprudent"], "15.1 20.1 12.9": ["anvil"], "6.2 14.0 3.2": ["belittled"], "8.0 10.5 6.8": ["gestured"], "6.3 14.1 5.4": ["duos"], "17.5 3.6 9.5": ["seesaw"], "11.2 15.0 3.4": ["nomads"], "1.4 0.6 -5.0": ["felicitated"], "1.3 -7.6 4.5": ["noncommercial"], "-0.4 11.5 7.6": ["habitation"], "-8.5 6.9 1.7": ["teamers"], "5.2 10.0 2.1": ["theorists"], "9.8 9.2 8.4": ["befriends"], "1.8 16.5 16.4": ["mildew"], "4.8 12.5 4.4": ["personas"], "-5.2 9.3 -0.8": ["connivance"], "10.3 5.6 10.9": ["heists"], "-6.2 0.4 4.6": ["undergarments"], "10.5 -0.3 4.5": ["hitches"], "1.5 6.9 8.6": ["illustrative"], "3.5 8.9 4.8": ["pew"], "8.7 9.1 35.8": ["coconuts"], "9.7 0.6 7.5": ["bioinformatics"], "3.3 -4.0 0.7": ["risque"], "0.6 21.2 2.7": ["troublemaker"], "1.7 6.1 -0.1": ["remarking"], "5.1 3.7 7.0": ["debauchery"], "0.1 5.9 6.4": ["matrimonial"], "7.0 0.3 -0.7": ["snubbing"], "13.5 19.6 2.8": ["gravitational"], "8.3 9.2 5.4": ["perforated"], "-2.1 14.5 0.4": ["duress"], "-0.9 6.2 2.0": ["fevers"], "8.6 10.0 1.4": ["jolts"], "1.2 13.1 4.5": ["headings"], "18.3 16.9 16.8": ["deities"], "1.8 2.1 3.3": ["bleaker"], "8.1 17.0 11.5": ["apostles"], "8.0 7.4 -0.2": ["multiplatform"], "14.8 9.9 24.3": ["marshmallows"], "15.8 13.6 9.4": ["taxman"], "12.4 21.7 16.2": ["proverb"], "2.6 2.2 8.0": ["hoarse"], "4.7 13.3 6.1": ["incurs"], "5.7 2.0 -0.8": ["thumbing"], "-1.2 7.1 -2.3": ["burgled"], "5.3 8.6 6.1": ["amply"], "12.5 0.1 8.7": ["resplendent"], "-5.1 -0.7 17.7": ["dentures"], "1.0 3.7 4.0": ["baffles"], "13.9 8.6 6.6": ["jabbed"], "3.9 6.2 0.6": ["reformation"], "-3.7 11.2 10.6": ["reasonableness"], "16.4 25.0 10.5": ["devilish"], "-2.9 4.9 13.9": ["weavers"], "7.7 5.7 6.2": ["bodybuilder"], "6.7 5.7 6.1": ["joggers"], "1.4 1.9 12.0": ["paclitaxel"], "12.3 5.5 9.1": ["shuffles"], "15.0 7.0 13.9": ["groaned"], "3.5 8.7 5.1": ["pats"], "11.3 20.0 9.5": ["yobs"], "6.0 5.9 8.2": ["tuba"], "-0.1 1.8 -2.1": ["cognizance"], "-2.6 9.8 -1.3": ["despatched"], "-0.1 9.9 11.7": ["perpetuates"], "-8.6 -0.1 3.6": ["detoxification"], "-4.4 11.7 8.6": ["circumstantial"], "4.8 7.7 10.0": ["lira"], "14.5 10.0 10.3": ["sq"], "0.8 1.5 12.2": ["ukulele"], "-2.4 4.4 3.8": ["carpooling"], "2.9 0.7 11.7": ["manicure"], "8.0 12.5 4.0": ["trudging"], "12.9 12.8 28.7": ["honeybees"], "10.2 7.6 1.6": ["urinated"], "7.8 0.3 3.3": ["peeked"], "7.6 10.4 13.9": ["tethering"], "14.8 18.8 13.6": ["parasitic"], "-8.7 23.1 3.0": ["ideologue"], "14.1 -1.1 9.6": ["unwrapped"], "8.0 9.8 5.5": ["arcs"], "2.8 12.4 6.1": ["biding"], "22.0 10.7 7.6": ["thicket"], "3.8 14.9 -2.0": ["perpetrating"], "1.8 10.2 30.1": ["thyme"], "3.3 24.0 2.7": ["disengage"], "7.3 10.6 11.7": ["porters"], "1.7 -2.6 -5.9": ["conceptualized"], "14.8 7.4 4.8": ["fraudster"], "-0.4 5.9 3.7": ["overflows"], "7.4 6.1 4.9": ["rectum"], "6.5 5.8 21.0": ["countertop"], "-3.9 15.1 7.7": ["mudslinging"], "-7.3 29.9 0.3": ["counterintelligence"], "2.0 5.1 2.1": ["cologne"], "19.8 12.6 10.9": ["warily"], "0.5 -0.6 8.3": ["feuded"], "9.7 2.5 1.9": ["eschewing"], "8.3 9.3 18.7": ["mutt"], "3.4 10.3 6.1": ["daze"], "-0.4 5.4 3.0": ["inhaler"], "-5.6 8.6 11.0": ["hem"], "-0.4 9.5 6.8": ["despairing"], "15.2 12.4 9.5": ["misfit"], "9.8 5.2 8.9": ["chutzpah"], "5.7 5.8 8.2": ["supernova"], "39.5 8.7 18.8": ["humongous"], "3.5 9.2 5.7": ["mumbled"], "12.9 7.1 9.2": ["zeitgeist"], "2.2 -2.3 8.8": ["scrapbooking"], "9.2 10.7 -1.0": ["ether"], "-5.3 10.1 5.7": ["redness"], "13.9 4.1 7.7": ["tangles"], "14.2 24.5 18.4": ["vermin"], "6.8 -4.5 12.8": ["cookware"], "0.6 6.3 16.4": ["quarries"], "17.8 10.9 10.5": ["domino"], "0.9 14.1 1.4": ["revalue"], "1.7 17.5 -1.1": ["antagonize"], "8.4 0.9 11.6": ["steadier"], "8.1 2.5 14.8": ["prefabricated"], "1.8 8.7 5.0": ["ragging"], "15.7 12.2 13.6": ["underbelly"], "5.6 8.8 2.2": ["razors"], "3.0 17.0 3.2": ["calibrate"], "-1.8 15.9 -5.4": ["interventionist"], "-1.8 1.2 1.9": ["encode"], "-7.7 -2.0 4.6": ["conditioner"], "14.5 1.7 14.7": ["kooky"], "10.5 29.9 4.4": ["annihilated"], "13.0 0.5 12.5": ["gyrations"], "7.2 12.2 12.2": ["prong"], "6.4 8.6 0.7": ["litigator"], "-0.3 3.3 3.7": ["reprized"], "19.2 27.0 23.0": ["battleship"], "6.7 2.2 0.6": ["hyperactivity"], "12.9 7.9 6.9": ["precariously"], "-1.9 16.5 1.0": ["contemptuous"], "8.8 3.1 25.1": ["cob"], "13.8 2.1 19.9": ["froth"], "4.7 2.8 6.9": ["longitudinal"], "6.6 3.4 2.3": ["groggy"], "0.6 9.5 2.8": ["coterie"], "-9.0 24.6 8.8": ["sustainment"], "7.9 9.4 -2.1": ["intersecting"], "7.3 19.1 -0.3": ["rationalizing"], "10.8 10.3 5.9": ["troika"], "-2.4 12.8 0.1": ["depreciate"], "3.2 2.6 17.0": ["panhandling"], "22.7 -0.2 4.5": ["fallers"], "0.0 8.2 2.7": ["elicits"], "23.9 2.1 24.1": ["lumpy"], "17.4 11.0 10.1": ["plummets"], "10.0 2.0 21.5": ["crisps"], "-0.1 14.8 6.0": ["theatrically"], "7.0 14.5 -3.3": ["codenamed"], "1.3 21.6 4.2": ["perversion"], "7.8 0.4 -0.2": ["ofthe"], "6.0 3.4 4.7": ["terminus"], "12.6 10.2 9.3": ["stiffen"], "7.6 21.3 3.1": ["pessimists"], "11.7 -0.7 7.5": ["subsiding"], "-1.5 0.1 7.4": ["featurettes"], "7.8 4.5 2.5": ["abuts"], "7.8 3.2 9.3": ["bristle"], "16.8 1.5 11.2": ["denting"], "8.9 2.2 2.2": ["rungs"], "0.5 12.0 3.8": ["geophysics"], "0.7 9.4 7.9": ["itemized"], "2.3 2.0 6.0": ["ameliorate"], "-3.9 9.1 5.5": ["blinkers"], "12.3 7.9 4.7": ["dogging"], "2.7 9.1 16.1": ["groves"], "6.6 10.2 10.0": ["slapshot"], "1.0 23.0 8.4": ["neocon"], "13.6 11.3 13.9": ["rump"], "8.0 0.8 8.7": ["hookups"], "9.2 7.6 3.0": ["acronyms"], "17.4 8.7 25.1": ["skewered"], "-3.5 14.4 -3.6": ["grieved"], "18.8 5.8 7.9": ["entwined"], "-7.8 -0.4 6.3": ["lodgings"], "6.4 6.8 4.8": ["yea"], "9.2 13.2 4.7": ["yearns"], "7.1 10.8 7.6": ["fucked"], "-1.9 9.8 24.8": ["birders"], "9.8 2.5 18.0": ["lunchroom"], "2.8 20.0 5.5": ["militarization"], "5.3 18.2 11.8": ["subconsciously"], "7.6 10.5 2.0": ["aeronautical"], "12.0 4.7 5.7": ["carpeted"], "5.7 -3.1 3.7": ["whet"], "7.8 10.5 12.0": ["holler"], "-0.3 2.2 7.5": ["tradesmen"], "-1.8 9.2 -0.3": ["theses"], "3.4 14.9 14.3": ["cannibalism"], "2.2 12.0 4.3": ["evaporates"], "4.7 7.9 42.9": ["estuaries"], "14.1 5.1 4.4": ["bankrupted"], "4.0 5.0 12.0": ["hoodies"], "-8.5 7.2 3.7": ["circumcised"], "18.7 7.4 11.1": ["tempest"], "12.5 11.0 24.3": ["slop"], "5.8 4.6 7.1": ["switchover"], "-3.0 2.5 1.1": ["prefect"], "7.1 14.7 -0.1": ["emanates"], "17.5 2.2 16.4": ["bovine"], "1.9 -3.1 4.1": ["plugin"], "1.3 2.8 7.1": ["lubrication"], "6.4 13.5 3.3": ["gatekeepers"], "13.1 7.1 -2.7": ["tarred"], "17.2 8.2 14.7": ["domed"], "-1.7 14.3 0.6": ["occult"], "4.4 3.1 13.2": ["corset"], "9.4 4.5 12.5": ["mashup"], "4.9 10.6 9.2": ["sensuous"], "9.3 -0.7 1.6": ["runup"], "7.2 11.0 15.1": ["thinly"], "-1.9 0.8 16.3": ["cardigan"], "-0.7 6.9 5.8": ["voltages"], "10.7 7.9 4.4": ["peppering"], "6.0 6.7 9.3": ["anchorman"], "8.2 8.9 13.1": ["wistfully"], "9.3 10.9 -2.5": ["ridiculing"], "0.6 6.9 3.5": ["reassessing"], "16.0 2.6 21.4": ["aqua"], "11.6 13.9 10.1": ["gall"], "10.8 18.1 3.4": ["twosome"], "7.5 -0.5 13.1": ["welders"], "-8.7 4.6 2.7": ["rehabilitative"], "5.4 8.4 -0.8": ["unequaled"], "4.5 -4.6 3.0": ["convertibles"], "6.1 11.4 9.7": ["authentically"], "-3.0 1.3 -2.6": ["payables"], "-1.0 7.2 1.3": ["treatise"], "15.3 4.9 20.4": ["appetizing"], "12.2 14.8 10.1": ["headfirst"], "7.0 9.6 8.2": ["skylights"], "5.5 2.0 6.6": ["aerosols"], "0.4 6.3 3.9": ["microbiologist"], "3.8 8.5 3.6": ["uppermost"], "-6.8 12.3 16.0": ["breadwinner"], "-0.8 9.1 -3.7": ["misstatements"], "3.9 14.2 -0.2": ["glorifying"], "10.4 5.3 6.7": ["spigot"], "-1.7 9.4 4.8": ["safes"], "10.3 -0.7 7.1": ["pr"], "-8.2 -7.4 4.2": ["supplementation"], "-3.0 6.9 1.5": ["confidentially"], "4.8 11.6 5.7": ["mumbling"], "-2.6 3.1 0.7": ["narrate"], "1.8 5.4 3.2": ["anlaysis"], "3.9 6.5 4.8": ["ostentatious"], "16.1 13.0 9.3": ["wilting"], "-3.1 12.1 14.3": ["castes"], "6.9 8.9 15.5": ["permafrost"], "11.3 3.2 4.5": ["overshadows"], "7.0 7.6 0.8": ["monetizing"], "-1.2 7.6 4.2": ["overstepping"], "-1.0 3.0 9.2": ["yarns"], "5.7 13.9 2.2": ["hideaway"], "10.3 2.2 5.6": ["wil"], "13.1 8.7 3.4": ["vuvuzela"], "9.2 2.6 3.8": ["reeks"], "8.8 13.4 5.2": ["vanishes"], "10.1 -6.6 3.9": ["sprightly"], "3.4 11.1 2.5": ["rediscovering"], "3.8 19.4 11.0": ["opportunism"], "-0.8 4.0 3.6": ["underreported"], "0.9 2.8 3.8": ["gravitate"], "0.2 19.3 9.6": ["corollary"], "-8.1 13.7 2.8": ["fullbacks"], "-5.1 9.6 3.7": ["reportage"], "2.7 7.7 5.5": ["crazier"], "-0.3 12.4 14.5": ["intrasquad"], "-3.5 8.5 5.2": ["eludes"], "-5.3 13.4 11.7": ["metastasis"], "21.5 11.3 6.4": ["bounding"], "18.7 25.2 6.2": ["arrayed"], "1.1 24.9 6.3": ["tenet"], "-5.5 8.6 0.3": ["harping"], "-10.0 10.4 10.5": ["superdelegate"], "6.0 13.3 8.4": ["auditory"], "4.6 20.8 7.0": ["maneuverability"], "18.9 5.1 4.5": ["rumbles"], "12.0 13.9 14.1": ["stinger"], "6.3 6.5 1.3": ["daunted"], "2.0 6.5 4.9": ["matchmaker"], "15.9 5.5 -3.8": ["sleeker"], "-8.3 0.5 2.0": ["backpacking"], "-3.1 -2.3 9.1": ["prizemoney"], "6.4 10.9 11.7": ["foils"], "11.3 8.0 16.1": ["poach"], "8.7 6.9 3.2": ["masterplan"], "15.0 0.4 4.6": ["distinctively"], "17.1 -6.7 5.9": ["paled"], "5.7 10.5 1.4": ["espousing"], "-2.9 0.9 3.7": ["ejections"], "15.9 6.3 8.1": ["bludgeoning"], "1.0 14.1 9.0": ["unorganized"], "2.6 10.5 -3.2": ["immunize"], "7.7 4.9 3.0": ["liquidators"], "13.9 21.7 7.7": ["stupidly"], "7.7 4.3 36.4": ["jade"], "6.1 8.3 8.2": ["encroached"], "0.9 9.5 -8.4": ["refuting"], "8.0 23.0 1.8": ["conflagration"], "-2.9 18.1 11.9": ["incumbency"], "4.1 12.9 8.7": ["superstitions"], "-2.5 6.1 -2.4": ["dueled"], "-0.5 4.4 27.5": ["gelato"], "8.3 -2.0 7.4": ["frowned"], "-10.6 1.1 8.5": ["duplexes"], "17.6 8.6 12.4": ["gnawing"], "9.3 12.8 6.9": ["viz"], "5.1 15.6 6.0": ["aperture"], "13.8 4.2 9.3": ["wiry"], "11.2 16.5 8.3": ["ungrateful"], "-0.6 3.8 16.0": ["laces"], "9.3 9.7 2.4": ["paradigms"], "8.3 4.2 4.2": ["shredder"], "-4.3 4.5 5.2": ["subplots"], "4.2 4.9 3.1": ["titlist"], "4.4 1.8 8.3": ["demure"], "-1.8 10.2 7.3": ["cyberbullying"], "4.9 12.2 4.0": ["disinfect"], "6.1 6.0 10.1": ["exteriors"], "0.5 -5.3 10.3": ["luncheons"], "-0.9 4.3 15.5": ["consecration"], "13.8 5.1 -1.4": ["restructures"], "5.0 7.9 14.4": ["refit"], "-3.1 -0.1 9.5": ["cervical"], "13.3 5.0 5.4": ["overseers"], "-2.3 5.7 4.4": ["distillation"], "9.9 -2.4 5.1": ["quid"], "15.7 3.5 18.1": ["fattening"], "27.0 6.1 8.6": ["hogging"], "-1.6 10.0 36.2": ["risotto"], "6.6 4.4 1.3": ["paraplegic"], "5.9 7.8 10.8": ["counterculture"], "-7.5 6.1 0.0": ["transacted"], "4.1 12.7 7.4": ["disembark"], "5.5 -1.5 -0.5": ["shunted"], "5.9 7.1 7.3": ["dependencies"], "2.8 4.2 15.7": ["kernels"], "-2.9 18.5 16.7": ["righties"], "-2.2 28.5 -0.4": ["informers"], "5.6 6.1 3.5": ["blushes"], "2.9 11.7 19.5": ["waterline"], "2.5 5.6 0.0": ["rejoins"], "-1.8 19.0 10.0": ["cliques"], "9.8 1.1 12.9": ["growths"], "3.9 9.1 5.0": ["layman"], "6.5 13.8 3.5": ["blurs"], "-7.2 16.8 0.1": ["dogmatic"], "15.2 12.5 22.2": ["tundra"], "1.5 4.5 12.2": ["fag"], "2.7 2.2 1.0": ["mopped"], "12.8 12.8 13.7": ["puns"], "9.1 5.5 10.7": ["frolic"], "-2.1 1.2 13.4": ["embellishments"], "1.7 4.8 4.6": ["extensible"], "13.7 8.7 5.9": ["forklifts"], "8.0 4.2 0.8": ["whitewashed"], "5.4 8.8 3.6": ["normalizing"], "1.3 3.4 27.6": ["tangy"], "10.5 3.9 18.5": ["bong"], "-0.3 11.2 -0.8": ["optometrist"], "6.2 10.0 5.1": ["duh"], "4.3 -2.7 9.7": ["masseuse"], "19.2 17.0 8.9": ["multitudes"], "20.9 3.3 -0.1": ["adorns"], "6.2 3.1 30.3": ["gumbo"], "-8.2 7.5 13.3": ["caregiving"], "2.7 6.6 5.3": ["inverter"], "5.7 11.2 -9.5": ["blackmailed"], "11.7 15.2 2.3": ["obscuring"], "10.8 8.3 5.1": ["teh"], "-4.3 8.0 3.6": ["cherishes"], "2.2 -1.0 7.8": ["capacitors"], "-9.3 8.5 11.8": ["pertussis"], "7.3 -0.7 5.5": ["worksite"], "7.9 12.9 7.6": ["ruckman"], "2.5 0.9 8.5": ["punchy"], "10.2 4.9 7.8": ["machinist"], "-0.8 11.7 6.9": ["presuming"], "7.4 1.3 7.6": ["compacted", "demain"], "-0.9 4.1 38.6": ["pesto"], "0.4 13.4 4.8": ["wisest"], "6.2 8.3 11.7": ["egged"], "10.4 16.4 12.1": ["joker"], "4.8 -2.0 3.2": ["encapsulates"], "9.7 0.4 16.6": ["truss"], "24.4 7.3 14.5": ["scuttling"], "-1.2 13.7 3.5": ["unsympathetic"], "8.6 9.1 25.8": ["spud"], "0.4 15.1 8.2": ["shyness"], "-3.1 -1.1 6.7": ["meniscus"], "4.5 7.8 9.3": ["extrapolate"], "5.1 1.7 11.1": ["leashes"], "13.4 -3.8 3.1": ["ons"], "-6.4 7.0 11.7": ["shortstops"], "-3.2 6.3 3.8": ["timeframes"], "6.6 5.7 3.3": ["drugging"], "0.2 -2.5 20.3": ["kegs"], "-2.2 4.4 15.8": ["snowfalls"], "-3.3 11.6 14.9": ["euthanize"], "12.9 7.1 8.1": ["wag"], "7.3 2.9 13.2": ["accelerators"], "3.2 11.6 4.7": ["certainties"], "1.0 10.1 -3.4": ["fabrications"], "10.8 4.8 10.2": ["cinch"], "8.7 -7.9 -0.1": ["spruced"], "4.0 4.3 6.3": ["worryingly"], "1.3 41.7 2.8": ["solider"], "19.3 13.4 25.9": ["vulture"], "-5.7 2.5 -3.8": ["evaluators"], "9.1 17.5 9.3": ["angelic"], "2.2 6.0 11.6": ["archeologists", "barrie"], "-7.8 -4.6 -0.3": ["remitted"], "21.3 1.2 6.3": ["menagerie"], "-4.5 5.7 6.9": ["forfeits"], "-5.8 6.4 15.4": ["freeholder"], "2.5 6.8 9.9": ["motorhome"], "-13.5 -3.0 18.1": ["yearlings"], "2.6 11.4 7.7": ["sinus"], "-4.5 11.2 29.1": ["upland"], "7.6 11.0 4.6": ["potty"], "15.6 7.0 4.9": ["recycler"], "-2.9 9.7 1.8": ["viii"], "1.8 22.0 7.0": ["sinner"], "7.2 23.5 4.8": ["fearlessly"], "0.5 -0.2 8.3": ["gm"], "11.4 7.5 1.7": ["hosed"], "10.3 6.3 5.0": ["nanotech"], "5.8 6.0 8.8": ["concertgoers"], "8.0 10.0 12.1": ["foreshadowing"], "-2.7 10.9 4.4": ["undress"], "6.7 9.0 5.4": ["inversion"], "-1.4 6.5 18.8": ["fender"], "0.3 13.6 3.1": ["manifests"], "9.1 14.6 14.0": ["shatters"], "3.2 12.0 8.2": ["backbenchers"], "0.8 1.1 6.7": ["trickles"], "-0.9 10.9 10.3": ["angrier"], "1.8 10.3 18.6": ["pomegranate"], "0.8 -0.7 11.8": ["gigabit"], "2.2 0.7 10.7": ["soiree"], "3.2 19.5 10.3": ["reloading"], "-2.5 3.5 3.5": ["videoconference"], "17.3 1.6 10.0": ["frolicking"], "10.2 11.7 1.7": ["strugglers"], "1.9 8.9 -0.4": ["trustworthiness"], "2.1 8.0 37.3": ["rhubarb"], "-0.2 21.8 3.8": ["unclean"], "15.5 16.5 22.7": ["icebergs"], "0.3 3.6 2.2": ["omits"], "2.2 9.5 0.1": ["newness"], "13.1 0.2 19.2": ["twine"], "8.5 14.9 5.8": ["bellowed"], "18.7 4.9 15.1": ["weirdly"], "1.0 2.2 5.0": ["burdening"], "2.2 8.8 12.1": ["nourishing"], "-4.0 7.7 12.8": ["downtowns"], "1.7 6.5 31.2": ["pilings"], "5.9 6.9 4.8": ["parse"], "0.6 1.9 7.6": ["breakage"], "13.9 7.0 18.3": ["oriental"], "9.3 3.8 3.3": ["disassembled"], "2.3 7.6 4.9": ["refilled"], "7.3 12.3 10.9": ["sim"], "5.3 13.0 12.5": ["recedes"], "4.6 -2.1 25.1": ["livers"], "7.0 16.3 4.5": ["laterally"], "4.9 4.0 15.6": ["dimes"], "8.6 5.2 1.4": ["murmurs"], "-0.1 13.3 8.0": ["impedes"], "10.2 8.6 2.4": ["magnetism"], "27.4 16.5 34.0": ["caterpillar"], "15.1 12.4 7.5": ["nook"], "4.6 2.1 9.7": ["banknotes"], "2.5 -0.7 3.2": ["contractually"], "8.6 6.3 11.6": ["throttling"], "8.2 20.8 7.7": ["mans"], "0.9 7.5 7.4": ["clergymen"], "20.0 6.7 8.5": ["yep"], "16.6 15.7 0.5": ["shaming"], "9.0 3.1 21.3": ["skewers"], "0.2 3.1 2.9": ["angina"], "7.0 6.0 7.9": ["squats"], "6.2 -0.8 3.3": ["clockwise"], "0.0 2.6 -0.5": ["targetted"], "-0.9 33.9 11.4": ["interceptor"], "-6.4 9.9 10.2": ["vocations"], "6.2 -1.5 5.4": ["starlets"], "5.0 6.1 1.1": ["catalyze"], "14.7 -7.0 6.3": ["forking"], "19.2 12.7 9.4": ["pylons"], "4.4 9.5 4.7": ["domicile"], "2.1 11.5 14.9": ["monsoons"], "4.9 10.6 9.0": ["multidimensional"], "2.1 8.9 6.9": ["stereotyped"], "8.3 10.7 2.6": ["alignments"], "-1.8 23.7 5.4": ["neoconservative"], "3.9 25.1 8.0": ["maiming"], "3.1 -0.6 -5.7": ["memoranda"], "-7.1 2.0 9.9": ["hysterectomy"], "8.8 6.0 12.2": ["posterior"], "2.1 4.5 2.3": ["drowsy"], "2.0 13.2 13.6": ["deadpanned"], "0.8 -2.7 8.3": ["braids"], "6.6 3.3 5.9": ["voyeurism"], "0.4 8.8 2.5": ["indiscretion"], "3.6 3.6 5.6": ["modifies"], "4.9 4.5 13.7": ["bachelors"], "12.3 5.3 13.4": ["grotto"], "15.6 9.8 11.3": ["umpteenth"], "10.2 14.8 17.6": ["beggar"], "-1.1 7.8 1.5": ["demurred"], "15.0 4.3 10.6": ["drape"], "2.7 0.2 5.5": ["televising"], "1.6 3.8 6.5": ["frets"], "1.7 6.0 -1.0": ["ashram"], "2.8 11.9 11.0": ["horseman"], "10.2 7.9 6.3": ["uplifted"], "-0.8 7.7 4.7": ["asthmatic"], "4.2 0.4 33.3": ["plums"], "-0.7 8.0 5.4": ["abutting"], "8.5 4.1 4.4": ["knifed"], "-9.9 8.5 7.8": ["reallocate"], "3.5 1.9 -6.0": ["shunt"], "20.7 8.7 20.8": ["munch"], "13.6 10.2 9.7": ["reputedly"], "-4.1 -0.3 4.0": ["adjourning"], "6.9 7.5 8.8": ["jive"], "4.8 6.4 12.8": ["gauze", "chapman"], "0.2 1.4 9.6": ["rectory"], "11.0 5.2 5.1": ["fads", "polymath"], "6.1 1.8 7.7": ["superlatives"], "-7.7 -0.2 9.3": ["sittings"], "4.0 10.4 -0.1": ["pressurize"], "12.5 16.5 8.9": ["buries"], "13.1 5.4 11.0": ["grizzled"], "6.1 4.5 19.1": ["sh"], "10.2 6.9 -1.2": ["carcinogenic"], "10.3 7.0 6.1": ["facsimile"], "8.9 8.6 3.2": ["permutations"], "-5.8 6.8 9.1": ["mcf"], "13.0 11.5 10.7": ["wilds"], "15.3 12.6 6.2": ["blithely"], "9.4 7.3 3.7": ["conjuring"], "-1.2 9.4 6.9": ["appendectomy"], "6.9 9.8 7.9": ["predefined"], "-3.4 -0.8 -4.6": ["conformance"], "-3.7 1.9 7.7": ["nightspot"], "12.6 9.2 4.0": ["inthe"], "-4.4 5.8 -2.5": ["instil"], "3.1 11.4 8.8": ["fashionista"], "6.5 -1.1 16.7": ["noontime"], "6.0 6.0 27.0": ["sailboats"], "7.0 7.9 -3.4": ["ejecting"], "5.1 3.5 11.2": ["blooded"], "6.1 27.2 12.7": ["lawbreakers"], "-9.0 17.9 11.4": ["stressors"], "1.6 12.4 2.5": ["latrines"], "-2.2 31.8 4.0": ["airfields"], "12.5 15.1 6.0": ["meekly"], "5.1 13.4 13.4": ["gangland"], "0.9 13.1 10.6": ["breakaways"], "11.9 11.3 11.0": ["caked"], "9.5 27.1 4.4": ["executioner"], "-4.4 10.6 8.2": ["baseband"], "9.4 -1.0 12.9": ["frazzled"], "10.5 -1.3 5.0": ["singed"], "-0.1 18.6 3.8": ["memorizing"], "-1.0 -0.9 4.5": ["edgier"], "8.4 2.3 7.8": ["supercomputing"], "-7.9 6.5 6.3": ["clotting"], "9.0 24.5 10.5": ["uncaring"], "12.7 28.3 6.4": ["crouching"], "1.4 5.8 3.4": ["penalizes"], "8.2 -7.6 7.4": ["removals"], "-1.1 15.0 0.3": ["perverting"], "14.3 39.6 6.4": ["annihilate"], "20.5 10.1 2.9": ["scoreboards"], "-8.8 -4.0 0.8": ["microcontrollers"], "11.8 -0.9 9.4": ["untangle"], "3.7 -6.4 1.4": ["busloads"], "-3.7 8.8 26.8": ["rye"], "10.2 -2.4 1.7": ["consultancies"], "3.5 3.7 12.5": ["chiropractors"], "17.1 8.1 5.0": ["miserly"], "2.5 16.1 6.9": ["alleyways"], "8.9 4.2 8.2": ["whittling"], "4.4 9.7 7.5": ["stooped"], "2.2 12.6 3.4": ["excellently"], "9.4 -2.3 20.3": ["husky"], "4.2 10.5 20.5": ["dune"], "6.3 7.3 12.5": ["porter"], "5.7 9.6 15.2": ["scalpel"], "2.9 7.4 1.9": ["universality"], "-0.0 27.1 8.0": ["snitch"], "18.9 6.9 5.9": ["boondoggle"], "2.3 9.3 6.0": ["opus"], "-2.5 6.0 7.4": ["thereabouts"], "-4.2 5.5 7.5": ["minibuses"], "-2.5 14.6 11.7": ["hesitating"], "20.8 27.4 8.5": ["indestructible"], "2.5 11.9 6.0": ["amputee", "fivesome"], "22.3 11.2 8.8": ["pulsing"], "4.3 1.9 6.4": ["degenerative"], "4.0 6.2 14.7": ["gentrification"], "4.6 7.0 0.3": ["concomitant"], "-0.3 16.5 5.8": ["depravity"], "5.5 -5.4 0.5": ["sprucing"], "1.1 7.2 21.5": ["margaritas"], "9.2 18.2 1.5": ["antipathy"], "3.5 10.4 3.7": ["postcode"], "3.0 9.3 7.7": ["underclass"], "11.4 15.4 5.5": ["geopolitics"], "-3.4 3.5 2.2": ["sidelining"], "9.5 11.5 2.4": ["slogging"], "3.9 2.8 12.7": ["eighths"], "6.8 12.0 3.9": ["policewoman"], "1.1 13.3 4.0": ["weariness"], "8.6 7.9 -2.3": ["relegating"], "9.3 -2.1 8.7": ["copier"], "9.1 4.4 11.0": ["wriggle"], "7.9 12.8 1.5": ["sanitize"], "2.0 1.8 3.6": ["criminalizing"], "12.9 1.6 33.6": ["buttery"], "0.6 6.9 0.6": ["thereon"], "9.0 9.1 6.2": ["outlive"], "-2.1 1.7 5.3": ["proviso"], "2.8 26.3 8.2": ["acquiescence"], "4.1 26.8 7.6": ["ruthlessness"], "0.7 3.8 10.6": ["bulimia"], "-14.3 7.1 1.9": ["administratively"], "8.0 4.2 4.4": ["oozes"], "5.5 23.2 13.8": ["underhanded"], "5.7 0.1 14.0": ["shearing"], "-1.8 -5.8 -4.6": ["recognitions"], "9.2 26.8 8.6": ["launchers"], "2.2 4.4 9.0": ["whiny"], "10.0 6.7 -0.3": ["lavatory"], "13.3 6.2 11.8": ["carpark"], "11.7 4.4 6.4": ["dawning"], "0.6 5.4 0.9": ["encoder"], "5.4 6.8 6.2": ["decompose"], "5.4 8.2 7.2": ["niceties"], "15.0 13.4 7.4": ["pelting"], "6.5 13.9 19.2": ["bluffs"], "13.8 2.7 9.1": ["fabulously"], "1.9 11.5 5.9": ["obsess"], "6.6 9.7 15.1": ["rotted"], "7.6 17.9 -5.8": ["desecrated"], "4.8 9.7 -3.3": ["captivate"], "-5.9 14.5 46.9": ["snook"], "4.1 5.5 -0.2": ["diverts"], "14.9 21.9 1.8": ["massing"], "7.7 -5.8 2.6": ["deeming"], "7.5 2.8 12.4": ["teaspoons"], "-4.8 13.1 3.4": ["inferences"], "2.0 20.1 3.0": ["postures"], "-3.5 -4.0 5.9": ["phthalates"], "0.8 2.5 3.2": ["diaphragm"], "14.5 3.9 0.5": ["romping"], "-1.6 -3.2 16.3": ["tuxedos"], "-3.5 7.0 -1.6": ["catalytic"], "-0.4 6.6 2.9": ["adhesion"], "15.1 7.5 4.9": ["india"], "8.8 7.4 1.2": ["atmospheres"], "-0.2 9.2 4.6": ["gusting"], "0.9 -2.4 8.4": ["haggle"], "1.9 16.1 8.1": ["domineering"], "7.4 6.9 25.2": ["watermelons"], "8.0 13.4 7.8": ["frailty"], "-0.8 2.7 7.0": ["headphone"], "0.0 18.6 4.6": ["pushback"], "0.5 4.5 1.8": ["slurred"], "12.3 6.4 13.7": ["concoctions"], "7.2 24.0 9.2": ["axiom"], "10.4 4.6 3.6": ["fractionally"], "3.6 1.1 -5.4": ["indemnification"], "19.6 7.1 8.0": ["monopolize"], "12.8 -1.6 2.1": ["nabs"], "7.3 7.0 5.6": ["centavos"], "-5.2 -3.2 2.4": ["sired"], "24.6 26.8 10.0": ["lair"], "5.8 -0.2 11.7": ["geneticist"], "7.6 2.7 5.5": ["thickening"], "-4.1 16.2 14.4": ["brig"], "11.9 13.1 1.7": ["capitulated"], "6.9 9.6 2.1": ["blower"], "4.0 11.0 3.0": ["preempt"], "7.8 11.0 21.6": ["pols"], "1.7 -5.6 8.5": ["cosmetology"], "-0.6 5.0 6.3": ["matron"], "16.4 4.5 9.3": ["jerked"], "8.0 5.0 0.6": ["snubs"], "-3.0 3.0 24.3": ["pastas"], "3.3 5.8 3.0": ["noninvasive"], "6.5 3.5 10.8": ["lifters"], "-5.1 8.0 0.7": ["bigamy"], "0.9 10.7 3.5": ["unadjusted"], "-2.0 4.7 10.6": ["timeslot"], "12.7 13.1 8.7": ["vertigo"], "2.7 15.6 5.2": ["unbeatens"], "14.3 4.9 10.0": ["cutest"], "8.1 2.5 11.4": ["pall"], "3.7 2.5 14.5": ["laminate"], "0.2 5.2 13.1": ["shawl"], "10.2 4.9 1.8": ["objectors"], "7.4 1.6 10.6": ["saddling"], "1.8 8.8 12.7": ["stringers"], "16.1 8.8 11.6": ["hammock", "appli"], "7.5 9.4 6.1": ["obliging"], "12.8 -1.4 3.3": ["spinoffs"], "6.1 13.2 0.8": ["dribbles"], "-0.0 9.2 5.1": ["canonical"], "-2.1 4.6 25.9": ["stainless"], "13.5 15.7 10.2": ["chaser"], "7.3 3.8 1.6": ["decries"], "8.5 19.9 9.0": ["hoodlums"], "14.7 12.0 30.5": ["oceanic"], "3.7 3.0 7.7": ["reassembled"], "9.7 5.2 6.8": ["squirted"], "-1.1 2.4 3.6": ["curriculums"], "6.8 4.4 7.4": ["pedaled"], "-3.7 -4.8 2.1": ["refereed"], "3.7 1.9 -4.7": ["circulates"], "7.5 16.9 12.7": ["wreak"], "-5.4 9.8 -1.4": ["deliverable"], "-5.8 15.3 3.3": ["unconsciousness"], "4.9 4.1 16.2": ["steelmaking"], "5.3 3.7 45.4": ["shrimpers"], "11.1 4.0 4.7": ["palatial"], "-8.6 0.0 4.0": ["coroners"], "8.0 3.4 17.0": ["moldy"], "-5.6 14.9 7.1": ["internment"], "12.4 1.9 11.7": ["prepackaged", "whacky"], "7.0 -2.0 8.1": ["infomercials"], "4.1 7.0 11.3": ["skewing"], "0.9 10.8 19.3": ["potter"], "21.6 20.2 5.1": ["galactic"], "5.1 13.7 14.0": ["entanglement"], "12.1 4.3 5.5": ["brainy"], "-7.9 10.7 6.4": ["handicappers"], "-0.2 2.6 11.3": ["outtakes"], "-1.3 28.8 3.6": ["ultras"], "21.9 8.4 13.8": ["blimp"], "10.1 8.3 5.5": ["dreamers"], "10.8 14.7 14.5": ["momma"], "-4.2 5.1 11.4": ["catchment"], "-9.8 -1.4 10.7": ["weeknights"], "0.4 6.5 6.9": ["impeccably"], "30.0 16.0 5.0": ["soulless"], "-1.0 17.1 -6.5": ["selflessly"], "2.3 7.5 11.8": ["undertones"], "-4.5 2.9 2.8": ["ppb"], "9.9 9.9 8.7": ["beguiling"], "-5.4 1.6 -1.6": ["ventilators"], "-5.9 4.3 5.6": ["unattached"], "7.2 10.8 6.3": ["profligate"], "1.6 -0.4 7.2": ["wilder"], "-7.2 1.4 11.8": ["triathletes"], "19.1 6.1 8.1": ["howled"], "15.4 15.5 7.2": ["animate"], "-8.6 6.3 6.1": ["selectivity"], "10.0 7.1 17.8": ["orangutans"], "1.4 18.7 7.8": ["misperception"], "4.8 17.4 1.7": ["abductor"], "19.1 9.2 0.3": ["goalposts"], "-0.0 4.2 18.8": ["norovirus"], "6.9 3.8 3.8": ["recreates"], "18.7 26.7 23.8": ["wasps"], "3.9 11.5 1.4": ["helipad"], "7.3 9.5 5.5": ["sidestepping"], "13.1 9.3 11.9": ["insipid"], "6.7 -0.8 8.0": ["fraying"], "8.2 6.9 9.9": ["gridlocked"], "18.6 10.3 12.4": ["sorta"], "15.0 17.2 4.1": ["ignominy"], "3.0 12.8 20.8": ["timbers"], "3.1 11.4 3.6": ["quarterbacking"], "6.1 15.4 14.9": ["desertification"], "-0.3 10.0 11.0": ["ebbs"], "14.2 11.9 9.8": ["darkening"], "1.1 2.9 7.1": ["tailors"], "1.6 15.3 10.9": ["hardness"], "2.5 2.8 8.5": ["overwrought"], "7.8 12.7 19.0": ["slicks"], "-7.3 8.3 6.6": ["internist"], "9.2 5.1 7.6": ["thermometers"], "1.0 4.6 9.0": ["mononucleosis"], "-9.1 6.2 13.1": ["provincials"], "5.2 3.5 0.4": ["noteholders"], "-3.9 18.2 -7.4": ["discrediting"], "1.2 21.4 1.3": ["resourcefulness"], "-1.9 5.7 6.5": ["seminarians"], "10.3 8.5 15.2": ["toasting"], "11.5 22.2 13.3": ["forts"], "3.7 1.9 0.8": ["honked"], "-8.8 8.1 4.7": ["transfusions"], "10.4 8.7 9.0": ["ditty"], "1.5 6.5 1.1": ["competently"], "2.5 6.9 14.4": ["discolored"], "6.7 1.2 4.3": ["threadbare"], "5.3 17.8 14.8": ["infestations"], "12.8 14.5 6.6": ["emblems"], "-6.3 7.1 8.7": ["nonsmoking"], "-6.0 15.1 6.5": ["lyrically"], "8.7 8.4 9.5": ["resets"], "2.6 31.1 8.3": ["resupply"], "16.5 9.9 18.6": ["crawlers"], "2.4 -1.8 3.8": ["adjudicator"], "-6.4 0.8 1.1": ["deferment"], "-5.9 6.7 13.7": ["feedlots"], "-0.6 0.2 6.2": ["overlapped"], "1.9 11.8 4.0": ["unbeknownst"], "5.8 4.4 9.9": ["ebbing"], "-0.3 5.3 7.5": ["tibia"], "8.3 20.6 16.6": ["fangs"], "5.1 2.9 16.2": ["frock"], "1.9 3.0 7.6": ["splint"], "10.5 4.9 17.6": ["cappuccino"], "16.8 10.1 14.3": ["ghoulish"], "3.1 11.3 11.4": ["assertiveness"], "12.5 12.4 11.4": ["brawn"], "4.6 1.0 2.9": ["debenture"], "9.3 16.8 6.9": ["aural"], "-1.5 9.3 7.0": ["underfunding"], "5.7 7.9 8.3": ["spoofing"], "3.6 26.1 -0.5": ["bravest"], "13.1 9.7 6.9": ["bottler"], "10.1 38.3 -0.2": ["liberators"], "12.7 23.1 12.1": ["dominion"], "-1.2 15.7 -7.6": ["dictation"], "0.6 16.9 3.5": ["deviant"], "4.8 3.1 6.9": ["reparation"], "-3.5 12.2 2.6": ["remediate"], "8.8 -3.0 6.3": ["threading"], "2.7 4.5 0.8": ["inexpensively"], "1.6 -3.6 9.0": ["reimburses"], "1.9 20.3 -1.5": ["jawans"], "10.1 6.7 11.2": ["tempering"], "8.1 2.6 20.7": ["logger"], "15.7 -1.9 6.8": ["eying"], "2.8 18.4 6.5": ["dispirited"], "5.9 0.1 7.9": ["catwalks"], "-2.5 -1.5 3.0": ["intermediates"], "11.8 9.2 1.4": ["flyovers"], "-1.0 11.0 -2.2": ["negates"], "9.2 12.8 37.0": ["chum"], "15.6 10.6 6.0": ["grubby"], "3.7 -8.3 9.9": ["fortnightly"], "1.7 13.4 0.5": ["lynched"], "0.5 12.6 3.8": ["agonizingly"], "8.8 3.9 6.5": ["loopy"], "6.9 19.7 6.9": ["escapee"], "5.7 15.5 6.7": ["preconceptions"], "-2.5 2.3 -2.4": ["glossed"], "22.5 8.0 29.5": ["mermaid"], "5.4 9.7 1.2": ["crisscrossing"], "4.1 6.2 26.5": ["ginseng"], "-3.3 5.3 13.7": ["irrigators"], "-3.4 10.9 10.0": ["aria"], "16.2 27.4 2.8": ["satanic"], "5.2 3.7 -1.1": ["disallow"], "10.0 20.9 7.6": ["allegory"], "8.4 28.8 0.3": ["heroically"], "17.1 15.2 22.5": ["pinball"], "-8.2 4.4 0.5": ["coauthor"], "3.5 19.8 9.5": ["misdirection"], "3.8 13.0 26.2": ["upriver"], "12.1 2.1 11.8": ["wheelbarrow"], "8.9 16.1 8.4": ["rears"], "-5.4 7.2 2.4": ["prejudge"], "9.7 30.6 5.3": ["saboteurs"], "2.2 10.1 4.9": ["meteorites"], "3.0 -2.0 -3.5": ["bedded"], "-0.1 8.2 10.9": ["nitrates"], "-0.5 13.2 -7.3": ["professing"], "-3.0 7.9 2.2": ["sympathizes"], "0.1 13.1 8.0": ["evacuee"], "14.1 16.5 3.0": ["zooms"], "12.4 9.3 38.9": ["seabirds"], "9.8 5.9 38.3": ["otters"], "6.9 12.6 3.7": ["awestruck"], "-6.3 17.3 8.1": ["improvising"], "10.2 11.5 10.3": ["jocks"], "6.1 18.5 24.9": ["mariners"], "0.5 7.9 -1.1": ["worthiness"], "5.6 9.3 10.2": ["unsophisticated"], "0.3 21.7 -0.1": ["brainwashing"], "-0.4 5.2 2.9": ["befell"], "1.6 3.4 14.3": ["mane"], "2.9 0.5 9.8": ["streetcars"], "6.7 6.5 1.7": ["permanence"], "-0.5 12.9 -1.2": ["bide"], "-3.6 7.8 -0.6": ["strove"], "15.0 -1.9 3.2": ["snafu"], "11.8 1.1 15.0": ["cooker"], "3.4 20.9 10.9": ["uninhabited"], "5.1 15.2 9.7": ["imprisoning"], "-3.8 2.2 4.4": ["novella"], "16.6 1.3 9.1": ["bobbed"], "-2.2 23.1 3.5": ["duplicity"], "6.7 3.6 23.2": ["sumo"], "5.1 7.3 3.6": ["congenital"], "1.8 3.5 11.3": ["decomposed"], "-4.7 1.7 18.2": ["replanting"], "10.0 3.3 15.8": ["snaring"], "9.3 12.5 7.6": ["doormat"], "-1.8 20.8 8.8": ["disunity"], "4.2 10.1 3.5": ["partitioning"], "-7.1 4.8 1.8": ["watchable"], "4.3 12.8 10.7": ["syllable"], "1.8 7.5 3.9": ["subcompact"], "-8.6 1.9 -0.1": ["dermatologists"], "-6.5 8.7 11.0": ["femtocell"], "-0.2 5.3 12.4": ["webmasters"], "5.3 12.9 3.4": ["echelons"], "-0.0 5.0 10.4": ["ko"], "5.6 9.0 24.5": ["lily"], "-2.6 18.4 2.9": ["deserting"], "9.1 12.0 5.3": ["colorless"], "2.9 3.8 6.9": ["hostesses"], "-3.0 11.5 2.7": ["gravesite"], "17.1 8.7 13.2": ["jutting"], "0.6 10.4 -0.1": ["thereto"], "1.4 8.0 4.4": ["reprogramming"], "5.0 7.9 5.4": ["retrospectively"], "6.7 4.9 3.3": ["superstardom"], "4.0 7.3 10.3": ["pt"], "-2.2 7.0 1.9": ["impairs"], "7.0 1.1 7.0": ["rapt"], "13.7 5.4 -1.7": ["dustbin"], "3.9 6.4 7.4": ["tabulation", "stigmata"], "1.2 0.6 5.5": ["proteomics"], "7.7 6.8 1.4": ["obsessing"], "4.4 3.8 7.1": ["opulence"], "3.4 10.4 -4.1": ["blackmailing"], "4.9 1.2 4.0": ["mollify"], "2.0 5.0 0.7": ["reinvesting"], "16.8 5.1 17.4": ["vat"], "8.2 1.7 -0.8": ["rioted"], "0.4 7.9 20.0": ["headwaters"], "3.8 7.5 6.3": ["grimaced"], "3.2 5.9 6.4": ["crooning"], "14.5 14.1 24.2": ["panther"], "30.5 14.7 11.5": ["titanic"], "15.5 4.4 6.9": ["techie"], "-2.6 8.2 8.2": ["moisturizer"], "14.1 2.0 14.0": ["bagger"], "1.7 7.6 3.0": ["irritability", "tranquillizers"], "-3.5 10.8 9.2": ["yatra"], "1.8 0.3 4.5": ["viewings"], "1.3 9.8 4.2": ["orientations"], "-6.3 9.1 10.5": ["cropland"], "8.8 10.7 3.9": ["massaging"], "9.8 8.2 14.3": ["ointment"], "10.0 16.1 1.6": ["envied"], "2.9 14.9 7.2": ["gloat"], "2.3 26.3 6.2": ["tribalism"], "25.5 8.4 8.1": ["nirvana"], "13.6 5.9 17.1": ["fatten"], "9.6 15.6 2.4": ["longitude"], "7.4 20.0 9.8": ["psychopath"], "8.5 20.6 16.2": ["underlings"], "4.6 14.1 4.0": ["constraining"], "11.6 3.7 13.2": ["machinists"], "6.8 7.1 25.4": ["patties"], "7.8 4.7 25.4": ["trawl"], "5.3 3.8 10.2": ["backpacker"], "-1.2 2.1 5.6": ["gelled"], "-5.5 8.6 -0.4": ["espouses"], "4.4 3.3 8.0": ["incandescent"], "-5.3 4.2 21.6": ["nonresident"], "7.6 -1.7 -0.1": ["circulars"], "-2.2 3.0 3.2": ["cogent"], "-4.4 0.7 14.9": ["folate"], "-2.3 10.7 2.2": ["paging"], "9.4 6.9 10.8": ["mire"], "0.4 5.8 -1.4": ["reasserted"], "0.3 5.8 4.8": ["dirtier"], "9.2 31.4 3.1": ["barbarism"], "6.3 3.0 9.5": ["photogenic"], "15.2 5.4 15.8": ["fancier"], "-1.0 3.8 6.0": ["overspend"], "3.2 6.4 18.3": ["downriver"], "-5.6 12.5 3.2": ["causation"], "3.4 4.9 2.1": ["sweated"], "6.4 4.1 10.7": ["statuette"], "22.2 0.1 16.6": ["shaker"], "3.6 3.9 1.5": ["facile"], "6.4 3.9 5.9": ["smoothness"], "7.7 3.2 3.3": ["ot"], "7.3 8.5 8.0": ["pings"], "0.1 4.0 7.2": ["fifteenth"], "-10.8 13.4 14.0": ["brucellosis"], "-0.2 -1.3 10.6": ["layaway"], "9.8 5.2 10.7": ["decomposing"], "0.9 3.4 25.7": ["lynx"], "17.3 5.4 7.3": ["sodden"], "14.0 4.4 5.1": ["reaps"], "5.5 4.3 23.3": ["pistachios"], "-3.3 2.7 2.2": ["retrofits"], "12.0 4.3 11.2": ["mosaics"], "2.2 4.9 2.9": ["anthropologists"], "-7.3 3.3 11.0": ["oilseeds"], "27.0 17.8 26.6": ["cockroach"], "3.4 16.6 9.0": ["flattery"], "3.2 13.1 6.6": ["miseries"], "3.3 12.5 6.0": ["escapism"], "2.8 8.2 14.3": ["nipples"], "5.1 8.3 8.3": ["disinterest"], "11.2 18.6 17.8": ["propellers"], "-4.5 -1.2 13.9": ["preschools"], "-1.9 5.1 8.5": ["criminalization"], "18.8 10.6 9.1": ["crummy"], "-6.0 16.3 0.9": ["conscription"], "12.5 12.6 2.1": ["sheikh"], "3.6 10.6 10.7": ["interlude"], "8.2 7.3 8.6": ["constructors"], "3.8 21.9 12.8": ["forecheck"], "-2.3 8.9 20.2": ["palates"], "16.1 0.2 7.9": ["scupper"], "4.7 18.7 11.5": ["stillness"], "1.4 2.7 15.5": ["cabinetry"], "-1.3 8.1 3.9": ["complimenting"], "10.9 8.9 8.7": ["prerecorded"], "8.7 7.3 6.2": ["touchpad"], "9.1 -3.2 14.8": ["lipped"], "1.8 14.7 10.6": ["offsides"], "19.2 11.8 6.4": ["discounter"], "5.4 8.4 11.4": ["pubic"], "7.1 14.4 6.5": ["confound"], "-0.9 9.3 12.3": ["boarder"], "11.7 7.9 12.9": ["mystifying"], "3.4 13.1 7.2": ["intelligentsia"], "-2.5 8.2 4.0": ["separations"], "5.5 -4.3 21.1": ["garnished"], "-3.6 4.7 11.3": ["mellowed"], "5.9 13.1 16.8": ["galley"], "6.7 4.6 6.8": ["polka"], "2.1 3.7 5.1": ["datasets"], "4.9 -1.5 11.0": ["bioenergy"], "3.1 10.3 2.8": ["flirtatious"], "9.9 -2.6 -1.0": ["relegate"], "3.2 12.8 12.5": ["northerners"], "1.5 11.1 10.3": ["embankments"], "-4.8 2.5 7.7": ["jitter"], "5.8 22.7 5.3": ["detest"], "12.3 9.1 -1.1": ["exchangeable"], "14.1 22.4 6.7": ["infinity"], "4.8 25.9 6.5": ["untrustworthy"], "11.8 7.9 7.9": ["glides"], "5.9 8.3 4.9": ["radiators"], "15.4 1.4 10.7": ["indigestion"], "1.1 13.6 6.5": ["inattention"], "22.1 4.4 13.5": ["granddaddy"], "1.2 5.4 5.5": ["decoder"], "16.9 11.0 12.0": ["scurry"], "27.4 21.3 34.1": ["toad"], "7.2 4.7 12.1": ["excavators"], "-2.5 16.9 3.0": ["disrespecting"], "4.9 11.8 10.6": ["moans"], "-0.1 12.4 6.2": ["transpires"], "9.9 10.8 4.4": ["laughingstock"], "-5.3 -2.4 3.7": ["repaved"], "2.1 9.5 10.3": ["devolve"], "-0.7 3.2 17.3": ["silks"], "-1.8 -0.4 8.3": ["intergenerational"], "7.1 10.8 7.2": ["ghettos"], "-5.2 6.0 0.5": ["logistically"], "-5.9 11.0 8.2": ["disciplinarian"], "1.8 16.6 2.3": ["mustering"], "8.3 11.5 -0.3": ["abbreviation"], "2.4 5.6 20.4": ["panto"], "0.9 -1.1 15.6": ["handicraft", "gla"], "4.1 3.2 3.5": ["medicated"], "0.4 -2.0 7.8": ["hashed"], "3.9 14.2 9.1": ["flack"], "7.0 6.2 10.8": ["whisker"], "-8.9 2.6 18.9": ["ewes"], "-0.1 7.3 0.9": ["hypothesized"], "15.9 -4.0 2.0": ["trebled"], "5.5 29.2 9.5": ["dungeons"], "7.5 12.0 8.9": ["jibes"], "1.3 15.9 4.2": ["multiplicity"], "11.1 9.9 20.2": ["arcades"], "-3.7 4.4 6.2": ["oeuvre"], "10.1 8.3 19.8": ["puppetry"], "12.1 13.5 -5.0": ["evangelists"], "15.6 6.0 9.5": ["oddest"], "1.3 15.5 -2.4": ["unseating"], "8.5 4.2 11.5": ["taster"], "6.9 13.6 6.2": ["inopportune"], "25.6 13.0 15.6": ["whirling"], "0.9 12.9 8.8": ["kibbutz"], "11.1 23.1 2.7": ["indomitable"], "-0.8 -2.8 0.6": ["academicians"], "19.8 6.8 10.7": ["chucking"], "-1.9 9.3 17.1": ["ripen"], "4.7 1.4 4.1": ["retrenched"], "7.2 17.9 3.9": ["infatuated"], "0.8 3.2 18.7": ["pantries"], "3.4 12.3 34.1": ["bluegill"], "9.8 4.2 1.3": ["jilted"], "13.5 1.0 7.3": ["stratospheric"], "12.1 2.3 7.3": ["spunk"], "5.8 16.9 -2.7": ["misadventure"], "10.2 14.1 6.0": ["slut"], "10.9 6.3 4.0": ["rekindling"], "5.3 8.8 17.0": ["fingernail"], "6.7 6.9 2.2": ["gushes"], "14.9 11.5 22.4": ["ox"], "3.5 16.7 44.5": ["trawlers"], "-3.9 4.0 4.9": ["erudite"], "12.2 29.5 19.8": ["torpedoes"], "-3.5 6.8 -3.3": ["synthesize"], "3.8 11.3 -0.3": ["suppresses"], "-3.7 16.2 6.5": ["outworked"], "10.3 6.5 16.7": ["baloney"], "13.5 8.8 -3.5": ["unaided"], "11.7 18.4 2.6": ["visualized"], "-2.1 11.7 3.1": ["linguist"], "8.5 5.8 10.2": ["thickened"], "-0.8 6.7 22.1": ["john"], "-7.8 5.2 4.5": ["rued"], "5.2 7.4 11.7": ["refills"], "11.7 6.5 12.7": ["jaunty"], "7.8 19.6 5.0": ["awakens"], "-3.3 4.7 10.7": ["commissary"], "-5.0 8.8 5.6": ["excommunication"], "6.8 10.8 -0.0": ["radiates"], "9.0 2.4 11.7": ["riotous"], "-0.1 1.9 2.8": ["couched"], "20.4 4.0 12.7": ["foundering"], "-5.4 20.8 9.6": ["pragmatist"], "2.4 3.2 10.1": ["spaceport"], "-3.5 -2.5 9.3": ["deferrals"], "13.2 4.2 8.8": ["microscopes"], "5.2 3.5 16.6": ["thong"], "20.5 5.9 14.2": ["canary"], "7.3 10.5 18.1": ["flyball"], "16.6 15.8 12.8": ["crumbles"], "10.5 13.0 5.8": ["pouncing"], "9.1 17.5 9.5": ["whereupon"], "2.6 -5.2 2.2": ["browsed"], "-3.7 10.8 8.3": ["mores"], "0.2 0.2 2.8": ["sadder"], "0.1 7.9 4.6": ["conceptually"], "6.4 14.4 8.3": ["ironies"], "-3.2 5.1 -0.8": ["thoroughness"], "-1.5 1.4 7.8": ["bioethics"], "10.7 6.2 10.4": ["sputter"], "2.0 17.8 8.8": ["saber"], "12.2 7.9 2.2": ["pilloried"], "10.8 11.3 19.5": ["beagle"], "0.9 16.2 2.3": ["proscribed"], "8.9 8.3 -2.6": ["disparaged"], "11.1 12.3 15.3": ["scavenging"], "7.7 9.7 12.8": ["felling"], "-2.1 27.0 19.1": ["archers"], "6.8 7.4 16.3": ["bib"], "-2.7 2.2 3.3": ["criminology"], "6.9 8.0 26.7": ["grizzlies"], "11.7 18.9 40.5": ["whalers"], "11.5 5.5 6.0": ["dispiriting"], "23.3 2.8 6.6": ["hurtled"], "-4.0 7.2 0.9": ["coincidences"], "8.9 10.9 6.3": ["delirium"], "-2.0 7.2 9.1": ["neckline"], "4.3 2.1 3.6": ["huffing"], "15.2 10.9 9.9": ["squirming"], "-1.0 5.5 -7.3": ["guarantors"], "-1.2 3.8 5.3": ["etch"], "1.3 7.6 1.8": ["falsify"], "5.4 9.9 7.9": ["gratefully"], "3.6 10.3 1.7": ["pagers"], "1.4 8.3 4.4": ["mowers"], "6.3 8.3 4.6": ["masturbating"], "8.0 15.3 28.3": ["grays"], "7.2 13.7 14.0": ["maidens"], "9.6 14.5 4.7": ["benevolence"], "-0.9 -6.2 3.4": ["residuals"], "11.3 14.7 3.6": ["spender"], "6.9 0.4 18.0": ["landscapers"], "12.4 9.8 9.0": ["spillage"], "-2.5 12.3 8.0": ["centrists"], "-2.3 23.9 8.6": ["secessionist"], "7.2 2.9 17.1": ["curlers"], "-1.1 11.5 11.5": ["tunic"], "-2.9 4.8 8.1": ["blotter"], "6.3 4.4 7.7": ["cyst"], "1.7 6.9 3.1": ["virtuosity"], "13.8 17.1 9.9": ["nonchalantly"], "-4.3 3.8 2.0": ["legwork"], "1.9 3.5 5.7": ["cess"], "6.0 10.4 4.3": ["unintelligible"], "6.1 -0.4 1.7": ["carloads"], "0.6 4.7 5.0": ["restlessness"], "1.1 2.0 5.3": ["fils"], "5.6 7.4 6.5": ["lamentable"], "-4.9 5.6 19.2": ["vintners"], "-0.6 12.2 -3.9": ["alkaline"], "-2.6 -2.3 6.1": ["interconnects"], "3.9 8.4 9.3": ["romantically"], "15.7 2.7 1.1": ["detachable"], "9.6 5.0 30.6": ["gills"], "-7.5 18.7 4.3": ["doctrinal"], "1.2 8.6 -1.8": ["disavowed"], "9.2 4.0 14.0": ["nag"], "3.3 -5.8 5.2": ["ado"], "0.1 13.1 -3.4": ["posses"], "-6.9 6.0 9.9": ["reallocation"], "14.5 8.8 11.7": ["hankering"], "6.2 1.0 -1.4": ["misappropriating"], "0.2 12.8 14.2": ["baserunning"], "6.7 -0.2 6.5": ["stilettos"], "11.9 -3.6 8.0": ["swank"], "3.4 10.3 10.2": ["valentine"], "6.0 -7.7 5.3": ["jazzed"], "7.5 17.0 11.4": ["sneer"], "8.8 14.6 14.0": ["speedboats"], "3.2 4.0 4.4": ["rummaging"], "10.0 11.5 -0.1": ["recluse"], "5.3 13.7 0.6": ["conversing"], "6.8 5.8 11.1": ["arty", "langa"], "-4.4 8.5 5.1": ["genotype", "pseudophakic"], "1.6 19.2 -1.3": ["deployable"], "-1.0 4.7 11.7": ["transients"], "3.9 6.5 6.7": ["humorist"], "4.8 8.1 10.3": ["goin"], "15.7 8.2 15.0": ["canopies"], "9.7 5.8 3.1": ["venerated"], "-0.9 6.8 3.7": ["matchday"], "-1.7 3.4 -6.3": ["dossiers"], "-2.7 8.0 2.4": ["surnames"], "19.8 -0.2 9.5": ["acrobats"], "-1.3 1.2 9.7": ["restorative"], "4.4 16.7 24.3": ["seamen"], "3.7 2.7 7.9": ["ar"], "-6.1 11.3 6.7": ["fluoridation"], "9.7 10.4 9.1": ["haphazardly"], "5.5 -3.7 6.9": ["juggles"], "6.7 3.2 11.9": ["doting"], "-0.7 34.7 3.8": ["disloyal"], "5.3 12.2 3.6": ["revolted"], "7.9 19.2 3.6": ["westerners"], "14.6 16.3 36.2": ["ferns"], "5.7 24.4 8.3": ["sandstorm"], "5.6 11.2 24.0": ["seafarers"], "17.6 6.3 14.5": ["enclose"], "9.0 15.2 5.2": ["remotes"], "11.2 -0.1 30.9": ["tortoises"], "5.8 11.1 1.8": ["expending"], "4.2 15.9 3.1": ["recapturing"], "-5.3 11.1 0.7": ["immunotherapy"], "-0.9 3.1 -6.8": ["fr"], "12.3 12.1 10.4": ["loveable"], "10.8 15.4 5.6": ["lobbing"], "20.4 13.1 11.5": ["kaleidoscope"], "8.9 4.5 1.0": ["liquidator"], "-2.2 3.0 3.0": ["rollovers"], "19.4 9.6 6.4": ["gizmo"], "7.8 1.7 6.5": ["dimmer"], "14.0 10.0 7.1": ["entranced"], "-5.2 4.3 10.6": ["overage"], "-4.9 8.8 -7.6": ["evaluator"], "9.7 8.5 8.8": ["entombed"], "16.4 22.1 19.5": ["microbe"], "0.2 14.7 12.8": ["basepaths"], "-6.4 6.2 2.4": ["tonal"], "-3.6 3.2 3.0": ["forint"], "8.0 9.4 4.1": ["kingmaker"], "12.9 3.0 6.2": ["gagging"], "-2.2 5.9 16.6": ["millers"], "7.8 -4.1 6.4": ["implantable"], "1.6 -1.6 8.3": ["nonpayment"], "13.3 12.9 7.7": ["nauseating"], "12.6 3.0 10.7": ["centerpieces"], "1.1 2.4 1.3": ["posited"], "-0.9 -1.0 4.4": ["timesheets"], "8.0 5.8 6.6": ["prospering"], "17.0 9.0 13.7": ["keystone"], "9.8 7.9 5.8": ["radial"], "1.3 3.8 10.1": ["creatives"], "9.5 2.9 7.8": ["huff"], "2.7 12.0 5.3": ["stateless"], "4.1 4.6 10.3": ["teary"], "17.5 15.2 11.7": ["morphs"], "2.5 13.2 9.6": ["insincere"], "4.7 3.4 5.0": ["bezel", "othe"], "8.9 17.5 13.0": ["sweetie"], "7.9 14.1 12.3": ["retard"], "10.0 5.8 0.1": ["cavalcade"], "0.6 7.5 13.2": ["landless"], "16.1 1.5 6.9": ["fridges"], "-5.9 -2.8 4.9": ["credentialing"], "10.7 -7.2 5.0": ["xxx"], "7.2 0.2 13.9": ["suede"], "11.2 13.9 7.7": ["supersonic"], "10.9 -3.3 -0.8": ["abounded"], "-1.8 30.6 -4.8": ["assassinating"], "5.0 15.8 2.4": ["rebellions"], "9.9 1.1 12.9": ["bloomed"], "-2.7 4.4 1.8": ["sensationalism"], "7.1 12.4 12.5": ["facemask"], "15.7 14.4 12.0": ["noun"], "8.4 10.1 5.2": ["headlamps"], "6.2 6.2 7.8": ["winced"], "-2.9 2.1 2.4": ["revivals"], "7.6 8.4 -4.5": ["negligently"], "-2.8 6.0 -0.5": ["musculoskeletal"], "-11.1 9.1 1.7": ["elaborates"], "3.8 11.3 1.3": ["panting"], "4.7 -0.6 14.6": ["ay"], "1.5 6.7 11.2": ["bazaars"], "6.2 10.6 0.2": ["keystrokes"], "17.0 29.2 8.6": ["conqueror"], "20.4 5.6 1.7": ["moneymaker"], "8.7 9.2 7.9": ["trudge"], "2.7 14.9 10.5": ["ballistics"], "13.1 5.1 13.1": ["goth"], "19.8 5.2 19.8": ["spiky"], "-3.4 -2.5 10.4": ["aquatics"], "14.6 1.8 5.3": ["prosaic"], "1.0 7.0 7.2": ["appropriating"], "-6.4 10.2 7.7": ["assaying", "resectable"], "9.1 3.7 13.8": ["sheath"], "-6.7 18.2 -1.6": ["demean"], "11.4 -0.8 6.3": ["twirled"], "6.2 8.2 -3.1": ["outlasting"], "2.2 7.8 14.9": ["governorships"], "17.9 6.3 14.9": ["beehive"], "-1.7 5.0 4.9": ["disinfected"], "5.0 3.1 11.1": ["ute"], "-0.9 16.6 1.4": ["retaking"], "10.3 21.1 9.8": ["truism"], "1.5 3.5 3.0": ["abut"], "7.2 6.1 5.2": ["lacing"], "19.0 24.4 10.6": ["pummel"], "-0.9 11.9 0.5": ["reintegrate"], "2.9 10.9 3.9": ["deafness"], "9.9 20.4 17.6": ["snowballs"], "0.0 0.7 7.3": ["railcars"], "-6.7 0.5 -0.2": ["unaddressed"], "13.8 9.7 36.3": ["gulls"], "-6.4 3.7 5.0": ["asymptomatic"], "11.4 -1.1 11.8": ["urns"], "-8.2 2.5 3.4": ["redshirting"], "-2.6 5.2 14.0": ["tattooing"], "4.2 6.7 5.5": ["attache"], "12.8 11.8 10.0": ["dang"], "4.6 4.6 2.8": ["neuroscientist"], "7.0 8.0 9.7": ["postelection"], "12.6 1.2 12.4": ["microsoft"], "-8.8 6.1 -1.6": ["opines"], "5.6 13.4 2.5": ["forsake"], "9.4 9.5 13.8": ["indeterminate"], "1.3 22.9 10.1": ["bluffing"], "18.1 13.8 16.1": ["bottomless"], "0.5 14.0 14.2": ["campfires"], "2.0 9.4 2.2": ["eminently"], "5.5 17.5 8.2": ["allergen"], "2.4 -1.2 1.2": ["misstated"], "20.7 15.1 11.0": ["slinging"], "10.7 12.4 23.2": ["snout"], "11.6 9.2 15.1": ["winch"], "11.5 6.8 7.3": ["goddesses"], "5.3 7.6 11.8": ["adulterated", "hov"], "11.3 5.3 14.4": ["kettles"], "9.4 8.9 4.9": ["navigates"], "3.7 13.6 25.0": ["chestnuts"], "6.6 2.4 19.3": ["abattoir"], "5.8 18.3 11.4": ["darkly"], "-3.6 10.0 6.5": ["fps"], "-3.2 4.4 5.6": ["bopd"], "11.0 7.2 16.5": ["blacktop"], "6.6 -3.3 5.5": ["disclaimers"], "7.2 30.3 6.7": ["totalitarianism"], "4.8 6.9 9.4": ["profligacy"], "5.2 8.6 10.9": ["musing"], "14.6 0.1 6.4": ["carting"], "8.6 11.1 7.6": ["pennants"], "-0.2 3.2 2.8": ["strictures"], "3.1 16.9 -1.3": ["wrongdoings"], "1.5 -0.5 2.8": ["inbounded"], "9.1 9.9 2.7": ["bulldozing"], "2.8 10.5 3.2": ["onside"], "15.3 19.8 4.2": ["flanking"], "0.6 12.3 -0.1": ["endeavoring"], "13.0 15.0 11.5": ["shrubbery"], "0.5 10.3 1.1": ["irritates"], "3.1 11.6 10.5": ["egotistical"], "6.3 11.0 5.8": ["nanoparticle"], "11.9 3.4 0.2": ["abortive"], "9.9 9.2 11.5": ["plumb"], "12.2 1.2 10.8": ["crimping"], "2.8 9.7 6.2": ["tetanus"], "12.2 5.7 4.1": ["faintly"], "8.1 18.3 8.3": ["enslavement"], "-0.6 14.3 7.0": ["perspiration"], "-4.6 7.0 5.6": ["relational"], "5.9 9.6 3.2": ["foreheads"], "2.2 0.6 10.4": ["districtwide"], "12.3 6.9 0.9": ["turnabout"], "6.1 21.0 8.9": ["cheater"], "8.5 -2.2 2.8": ["twisty"], "4.9 3.3 1.1": ["gymnasiums"], "18.4 16.8 13.3": ["inexorable"], "8.0 5.4 7.9": ["meander"], "15.6 16.7 5.7": ["radiating"], "-2.4 3.8 4.7": ["viscosity", "oncogenesis"], "8.1 0.5 5.5": ["rands"], "0.9 2.0 7.7": ["keepsakes"], "8.4 16.6 6.4": ["agitate"], "13.8 7.9 7.8": ["vacuuming", "teaboy"], "12.1 3.7 3.5": ["solidity"], "0.9 15.0 -6.3": ["slanderous"], "10.5 12.1 4.1": ["nomenclature"], "16.0 12.7 15.9": ["squirt"], "5.5 14.5 12.3": ["forehands"], "0.6 23.5 4.4": ["commandment"], "5.1 12.3 20.1": ["pout"], "0.8 3.4 7.5": ["xx"], "-7.1 6.6 11.9": ["roading"], "0.2 4.1 12.9": ["freeholders"], "-4.3 10.7 -7.8": ["distanced"], "-2.2 -2.4 3.0": ["refile"], "3.3 3.5 4.8": ["parsing"], "6.9 14.2 11.2": ["corroded"], "-0.7 4.8 7.3": ["prorated"], "-0.0 11.5 3.0": ["silences"], "11.7 -0.4 4.4": ["inset"], "7.0 0.2 17.0": ["cadavers"], "18.6 2.1 14.2": ["origami"], "6.3 9.8 13.8": ["landlady"], "3.6 2.3 -1.1": ["retraced"], "6.7 2.4 1.3": ["contravened"], "10.2 -0.3 4.8": ["petered"], "2.4 16.1 4.3": ["abhor"], "12.0 39.9 8.4": ["imperialists"], "9.4 10.1 15.0": ["crusher"], "-0.5 11.1 5.7": ["attics", "proffesional"], "7.1 -1.4 10.5": ["languid"], "12.0 2.9 6.0": ["midsized"], "8.5 13.4 13.5": ["ala"], "13.3 -1.3 -0.7": ["vies"], "6.0 16.1 7.8": ["pretensions"], "-0.9 -0.3 7.9": ["reauthorize"], "3.4 32.4 6.7": ["neoconservatives"], "3.5 4.5 13.8": ["slushy"], "-3.6 6.4 1.3": ["remixed"], "21.1 20.5 18.7": ["slingshot"], "1.2 3.7 8.5": ["walkable"], "9.7 10.0 8.4": ["quantifying"], "10.7 3.9 10.8": ["spandex"], "-1.0 9.7 2.0": ["womanizing"], "6.0 15.1 5.3": ["epics"], "8.5 12.4 14.1": ["guillotine"], "4.6 8.4 14.1": ["est"], "10.6 15.1 14.3": ["grimace"], "1.5 14.0 1.7": ["brags"], "8.5 18.2 3.3": ["ragtag"], "1.4 11.3 8.7": ["worships"], "4.3 2.2 9.2": ["mainframes"], "6.6 3.0 2.6": ["symphonies"], "-1.3 6.7 4.2": ["criminalized"], "19.0 3.6 7.2": ["funnels"], "8.6 12.5 7.0": ["prick"], "11.5 6.0 19.2": ["nickels"], "11.6 -0.1 16.6": ["carnivals"], "8.0 7.3 3.2": ["dislocating"], "4.2 10.0 2.2": ["tirades"], "9.7 11.4 2.6": ["minders"], "11.0 4.5 8.3": ["beaters"], "10.7 1.8 8.1": ["enliven"], "14.1 14.4 15.3": ["ark"], "17.5 6.4 3.2": ["fluttered"], "4.7 5.1 36.7": ["figs"], "-1.2 22.8 9.3": ["disobedience"], "0.2 18.4 3.1": ["nonmilitary"], "13.0 5.9 6.9": ["pilfered"], "5.0 7.8 23.9": ["islets"], "15.2 1.8 13.7": ["quintessentially"], "-2.0 6.6 5.7": ["wides"], "8.3 9.2 -4.6": ["rechargeable"], "16.7 -8.1 6.0": ["nix"], "8.7 6.5 19.5": ["divvy"], "3.6 1.3 -1.4": ["misidentified"], "13.0 8.1 6.5": ["steadying"], "2.9 1.7 15.2": ["bullfighting"], "9.3 6.2 -0.6": ["restating"], "2.1 8.8 16.0": ["snowplow"], "13.7 21.9 10.5": ["metaphorically"], "-2.1 16.1 5.7": ["rudeness"], "8.6 9.3 2.1": ["reconfiguring"], "-2.2 -1.2 -0.2": ["misspent"], "-3.5 4.2 65.3": ["rockfish"], "-5.8 1.0 2.5": ["runnerup"], "-9.6 23.1 16.4": ["interdiction"], "-2.3 2.2 5.0": ["revote"], "-1.4 6.3 -1.5": ["pharmacological"], "6.6 12.3 8.2": ["fandom"], "2.4 7.8 32.8": ["meatloaf"], "9.0 14.4 4.7": ["inaccurately"], "8.6 8.1 0.2": ["schemed"], "6.6 10.6 2.5": ["explanatory"], "6.6 -2.8 4.0": ["busload"], "9.9 18.8 4.1": ["penetrates"], "0.2 2.6 9.4": ["overproduction"], "15.0 1.1 6.1": ["lampooned"], "12.6 11.6 8.7": ["darken"], "10.9 3.5 7.7": ["bookend"], "-5.3 12.8 12.8": ["patriarchal"], "-3.8 11.6 0.1": ["mindsets"], "-2.5 13.3 29.5": ["pheasants"], "-3.6 2.7 1.3": ["endoscopy"], "3.0 5.3 10.5": ["rainstorms"], "4.1 1.3 7.1": ["tardiness"], "8.4 21.9 0.7": ["tormenting"], "0.1 6.8 6.1": ["reverend"], "14.2 1.5 6.4": ["watertight"], "2.1 -0.3 7.5": ["overrode"], "-0.1 6.4 14.2": ["sanding"], "13.4 -0.4 4.3": ["semitrailer"], "0.8 0.5 2.9": ["defers"], "8.1 10.1 -5.7": ["crusading"], "3.6 8.9 6.0": ["unfocused"], "-2.6 11.7 8.0": ["tolerates"], "-2.3 7.4 16.3": ["lawmaking"], "16.2 11.9 9.5": ["wallop"], "1.7 23.5 7.5": ["strategize"], "27.3 7.3 9.2": ["wonderland"], "2.8 3.6 17.4": ["chippy"], "3.5 2.3 8.0": ["buckles"], "8.8 1.7 3.7": ["treadmills"], "12.2 7.7 4.5": ["chirping"], "8.4 9.2 1.9": ["cordless"], "10.7 7.1 21.1": ["trifle"], "14.2 1.8 20.8": ["heaping"], "-2.5 1.1 13.7": ["striping"], "-6.5 9.5 6.2": ["incisions"], "-5.9 30.9 2.7": ["deserters"], "5.4 5.3 17.2": ["rickshaw"], "11.2 15.6 8.8": ["grimacing"], "-3.6 6.3 6.2": ["abided"], "6.1 25.2 10.7": ["bourgeoisie"], "6.5 9.0 11.5": ["aft"], "2.0 13.7 13.6": ["linemate"], "6.1 5.9 3.5": ["multiparty"], "2.8 5.3 15.4": ["sawmills"], "3.5 21.7 7.4": ["submissive"], "13.5 -2.0 -1.5": ["digitizing"], "4.3 11.6 -1.0": ["secreted"], "5.2 0.0 4.0": ["reintroducing"], "12.3 15.3 -0.3": ["unmasked"], "9.1 6.9 5.5": ["keenness"], "5.2 0.0 18.5": ["bleached"], "3.2 11.5 1.1": ["connotation"], "1.8 15.9 0.4": ["destinies"], "2.6 20.4 13.0": ["backwardness"], "13.8 3.0 21.0": ["milkshake"], "17.1 22.0 19.8": ["twitch"], "9.3 -1.1 0.9": ["belie"], "0.5 6.4 7.7": ["triceps"], "22.2 6.3 11.3": ["maven"], "13.7 21.8 3.8": ["visualizing"], "16.8 8.4 6.8": ["crannies"], "11.4 1.0 11.4": ["lark"], "0.2 7.8 9.1": ["sisterhood"], "6.0 15.8 30.5": ["skiff"], "11.3 1.8 -2.2": ["unbundling"], "-12.0 0.3 23.7": ["sailings"], "-1.1 13.4 6.8": ["estimations"], "11.2 11.1 6.6": ["peerless"], "12.4 18.6 18.9": ["diggers"], "0.0 13.8 -2.0": ["denunciations"], "6.4 12.1 5.0": ["reloaded"], "6.8 3.6 25.2": ["riverboat"], "21.2 1.8 6.7": ["swish"], "-8.2 5.4 6.8": ["collegial"], "9.7 14.9 5.8": ["inordinate"], "1.7 8.7 16.7": ["snowmaking"], "22.4 11.8 29.6": ["hare"], "14.0 3.5 10.1": ["voluptuous"], "-5.2 0.4 19.0": ["calving"], "-7.6 7.2 5.6": ["duplicative"], "6.4 0.8 3.0": ["unpack"], "3.6 8.0 12.1": ["bantamweight"], "2.5 10.1 11.6": ["cruiserweight"], "-2.1 0.8 3.2": ["kinesiology"], "1.1 14.0 2.1": ["madrassa"], "-5.5 5.9 -7.1": ["polygamist"], "1.4 3.8 7.5": ["litters"], "10.1 20.1 3.3": ["sneezes"], "5.1 -2.1 8.0": ["bp"], "-2.0 4.2 18.2": ["iwi"], "-0.8 -1.3 1.1": ["transcoding"], "-1.1 -0.7 -0.2": ["backburner"], "20.6 1.2 6.1": ["tottering"], "6.2 13.3 0.8": ["vociferously"], "18.5 6.3 12.5": ["kiddies"], "0.8 2.3 15.5": ["strapless"], "6.7 8.6 -2.6": ["pacesetter"], "14.7 3.1 -0.7": ["monopolized"], "4.0 21.9 4.5": ["interdict"], "9.7 11.6 5.7": ["changeable"], "14.9 4.2 7.1": ["homely"], "-3.5 19.6 2.0": ["muslim"], "4.3 12.6 28.0": ["omelet"], "0.7 1.9 8.5": ["wa"], "10.6 11.8 6.0": ["drenching"], "11.5 5.7 7.5": ["scalding"], "16.4 17.5 6.7": ["unholy"], "3.6 3.2 0.1": ["bogeying"], "6.5 19.1 8.1": ["spiteful"], "5.0 7.9 7.6": ["skylight"], "2.4 15.9 9.2": ["inclinations"], "15.6 12.4 7.7": ["scampering"], "1.1 13.0 9.1": ["allusions"], "-0.7 9.4 6.4": ["uptempo"], "7.4 0.0 3.6": ["terabyte"], "12.1 11.2 10.7": ["aristocrat"], "10.9 8.4 10.8": ["snooze"], "15.8 9.5 9.9": ["crescent"], "15.5 26.9 11.4": ["citadel"], "-5.8 6.9 5.6": ["deliberative"], "3.3 0.5 11.7": ["falloff"], "15.9 5.8 2.2": ["patenting"], "9.3 7.4 12.5": ["cantankerous"], "-1.2 4.7 18.6": ["ripening"], "-0.1 4.4 14.2": ["redirection"], "-7.9 8.2 17.0": ["replant"], "0.8 8.0 5.1": ["deejay"], "20.1 9.5 12.0": ["lattice"], "10.9 16.9 30.1": ["shallows"], "11.0 10.1 -0.0": ["exhorting"], "5.0 21.9 4.0": ["abominable"], "6.6 12.0 8.3": ["autoworkers"], "-1.9 4.7 10.2": ["perchlorate"], "0.6 12.4 7.9": ["exorcism"], "9.0 16.6 5.8": ["obscures"], "10.5 12.1 9.1": ["groupies"], "2.9 2.3 7.5": ["lucked"], "5.0 13.7 0.9": ["catharsis"], "8.4 14.7 13.1": ["snob"], "-9.8 -0.1 1.0": ["deletions"], "5.7 6.5 16.3": ["aboriginals", "khol"], "7.6 3.3 8.1": ["padlock"], "-2.1 5.2 6.4": ["genealogical"], "2.6 -1.9 4.3": ["offtake"], "-0.5 3.3 4.1": ["braked"], "-0.8 10.6 5.3": ["ix"], "4.9 6.8 -2.6": ["feelers"], "-5.3 9.4 -6.5": ["disowned"], "12.4 1.7 12.2": ["java"], "4.7 3.9 6.9": ["dulled"], "6.7 6.0 14.7": ["kindergartner"], "11.0 10.0 3.6": ["funder"], "8.0 11.0 8.6": ["inhabits"], "-2.6 6.1 11.2": ["demographer"], "3.5 6.7 13.7": ["drawl"], "7.8 4.6 13.0": ["boomer"], "-0.5 4.4 -0.0": ["collateralized"], "6.0 6.0 6.6": ["allrounder"], "3.7 7.9 -2.0": ["reaffirmation"], "17.1 5.5 7.5": ["balky"], "-1.3 -3.8 24.7": ["medallions"], "16.1 6.4 14.5": ["clamshell"], "14.5 12.8 14.2": ["putrid"], "14.6 -1.3 6.5": ["shambolic"], "6.4 6.8 10.5": ["enticement"], "4.3 20.8 -1.1": ["irritants"], "-1.2 5.8 6.9": ["putters"], "8.4 4.9 13.7": ["roofed"], "14.1 6.3 10.6": ["gleam"], "15.4 6.8 14.1": ["tiled"], "1.3 13.3 5.1": ["neglects"], "9.2 2.5 8.2": ["befits"], "5.2 7.2 6.2": ["goofing"], "12.7 -5.0 5.9": ["stapled"], "5.2 5.9 4.1": ["les"], "1.1 1.9 -1.6": ["bankable"], "9.2 11.3 1.6": ["cased"], "2.3 4.4 9.8": ["indulgences"], "9.8 4.8 6.5": ["punctuate"], "12.6 17.4 3.5": ["beep"], "4.3 6.5 14.8": ["pliers"], "-1.1 2.9 8.9": ["congresses"], "5.1 8.3 6.7": ["popes"], "5.4 12.6 5.8": ["malleable"], "1.1 1.8 1.1": ["acceded"], "-5.3 5.2 9.6": ["dancehall"], "5.5 0.9 16.6": ["banding"], "11.2 2.8 3.3": ["megachurch"], "3.4 4.7 7.2": ["theres"], "3.6 4.8 7.2": ["workaround"], "10.5 19.4 23.6": ["peck"], "3.6 6.7 8.1": ["microblogging"], "2.5 10.4 15.3": ["girlie"], "11.3 22.0 2.5": ["conquests"], "-0.5 7.1 -1.3": ["impartially"], "6.5 0.2 4.3": ["yearend"], "11.3 5.0 4.7": ["hypermarkets"], "0.2 16.4 2.6": ["politburo"], "13.2 4.8 2.6": ["hoardings"], "-0.7 2.6 14.8": ["hydrocodone"], "4.1 8.3 13.3": ["arboretum"], "0.6 2.9 6.5": ["barbers"], "2.4 6.8 13.8": ["carb"], "6.7 15.3 4.1": ["naively"], "2.7 11.4 29.7": ["lighthouses"], "1.1 11.4 4.2": ["depreciating"], "6.7 7.8 25.0": ["felines"], "8.9 5.1 5.8": ["datacenters"], "10.3 9.8 -0.9": ["elliptical"], "8.3 16.6 8.2": ["inhabiting"], "4.1 8.7 4.9": ["cringed"], "5.4 14.4 3.3": ["courtyards"], "8.3 6.5 4.6": ["serenade"], "14.4 3.2 8.8": ["squealing"], "18.0 2.5 17.7": ["shriveled"], "23.6 0.4 2.9": ["consortiums"], "-13.6 12.3 -0.6": ["audiobook"], "2.5 12.3 1.4": ["endear"], "1.4 2.3 6.6": ["chafed"], "-2.4 14.5 0.1": ["distancing"], "-8.6 12.7 0.1": ["coachable"], "5.2 8.4 12.7": ["concoct"], "15.5 7.2 5.8": ["jostle"], "13.7 33.6 3.5": ["pursuers"], "11.3 23.9 10.2": ["kingdoms"], "8.3 6.0 -2.1": ["cumulatively"], "-4.0 9.9 15.2": ["gonorrhea"], "7.1 6.7 9.8": ["portends"], "1.8 4.6 4.7": ["nurtures"], "18.7 14.3 11.2": ["biggie"], "18.9 8.0 10.7": ["merrily"], "0.8 3.7 3.3": ["businesswomen"], "8.3 1.3 10.1": ["castings"], "10.0 6.8 11.7": ["dab"], "14.6 -0.9 3.0": ["imbroglio"], "-2.5 13.8 0.6": ["polygraph"], "8.8 1.8 11.8": ["stoppers"], "3.6 8.7 13.8": ["bandana"], "9.2 14.9 6.0": ["rudely"], "8.1 15.3 20.1": ["reeds"], "1.3 30.5 0.7": ["oppress"], "11.6 16.2 5.7": ["whoops"], "13.0 0.9 15.7": ["chipper"], "3.1 8.9 -2.1": ["litigating"], "0.3 9.5 18.3": ["eights"], "7.0 7.1 8.2": ["marvelously"], "3.1 14.9 -3.7": ["synchronizing"], "-7.9 12.6 4.8": ["determinants"], "6.0 3.9 4.3": ["inboxes"], "11.7 0.7 7.1": ["beefs"], "3.0 9.9 9.9": ["inconsiderate"], "-2.1 2.5 2.1": ["headscarves"], "16.6 3.2 23.0": ["lollipop"], "-8.5 12.8 6.2": ["quarrels"], "9.2 -0.4 5.8": ["tollway"], "12.4 3.9 28.6": ["flake"], "6.2 12.1 4.1": ["coverup"], "9.5 0.4 17.7": ["banded"], "-0.6 1.6 13.6": ["taxicab"], "0.0 5.9 7.2": ["ecclesiastical"], "-5.5 2.5 -1.7": ["serialized"], "8.8 -1.1 1.0": ["privatizations"], "2.2 0.4 9.5": ["decoupling"], "5.9 3.8 1.7": ["buttressed"], "-1.4 6.2 22.0": ["houseboat"], "10.1 1.1 11.5": ["burnished"], "0.2 4.1 3.2": ["dpi"], "8.1 11.9 1.4": ["irresponsibly"], "12.9 29.8 6.5": ["exterminate"], "7.2 10.2 -0.8": ["indefatigable"], "4.3 8.3 7.1": ["appendicitis"], "-0.5 4.4 4.7": ["boreholes"], "0.7 3.7 8.2": ["lint"], "5.8 2.9 2.9": ["percolating"], "5.1 19.4 7.6": ["homicidal"], "7.6 5.5 11.3": ["motored"], "1.2 0.7 62.3": ["abalone"], "5.8 8.8 7.2": ["dramatize"], "3.0 6.1 10.4": ["synchronous"], "-5.1 5.3 8.6": ["overridden"], "10.5 14.4 8.3": ["bores"], "11.6 11.7 3.4": ["moronic"], "2.7 1.2 2.9": ["overpayment"], "4.2 2.1 21.4": ["pinkie"], "0.2 3.4 3.6": ["bequest"], "3.3 10.7 2.2": ["overplayed"], "9.5 19.2 10.8": ["onrushing"], "-0.5 18.6 10.1": ["lawmen"], "-9.1 7.5 17.8": ["ales"], "4.7 16.3 2.2": ["emissaries"], "6.7 6.2 -2.1": ["ransacking"], "16.9 10.6 10.2": ["tableau"], "4.0 10.3 4.1": ["drivel"], "13.1 0.8 4.0": ["sweatshop"], "9.9 9.2 5.9": ["bobble"], "3.3 -4.0 -1.9": ["conditionally"], "2.5 16.6 -1.3": ["consoling"], "8.2 8.0 8.2": ["inventiveness"], "5.6 3.4 25.1": ["fig"], "4.1 12.1 6.6": ["undeserving"], "19.0 9.4 5.7": ["eons"], "13.1 7.6 14.5": ["hooves"], "12.5 2.9 4.4": ["dubs"], "-6.8 7.5 7.0": ["hamstrings", "speechwriting"], "4.4 3.8 10.8": ["megabyte"], "22.4 9.4 13.1": ["impaled"], "-2.1 5.3 6.0": ["scrumhalf"], "1.6 25.1 1.5": ["tortures"], "5.6 10.4 7.7": ["woozy"], "4.6 24.4 -0.1": ["conspirator"], "-5.1 11.1 17.7": ["biosecurity"], "-1.1 0.6 17.0": ["bantam"], "6.4 2.2 2.0": ["dragster"], "7.7 4.7 4.7": ["wagging"], "6.7 2.8 14.0": ["pooches"], "4.6 13.4 9.2": ["commas"], "1.1 -4.4 -1.4": ["adjudicate"], "-9.5 8.7 19.7": ["regattas"], "14.2 8.2 9.5": ["backflip"], "29.4 7.3 15.4": ["innards"], "0.6 18.3 9.2": ["precepts"], "1.4 4.9 20.5": ["pedicure"], "14.8 4.1 17.8": ["dainty"], "-5.5 9.1 14.6": ["falsetto"], "6.4 -1.0 11.3": ["ta"], "-4.6 14.1 0.1": ["unbecoming"], "-3.1 -0.9 1.7": ["admissibility"], "-1.1 7.3 6.2": ["contusion"], "4.6 4.6 4.8": ["eschews"], "12.8 3.2 8.8": ["arthritic"], "6.6 2.8 7.1": ["resveratrol"], "0.1 6.6 18.4": ["timberland"], "7.7 8.9 10.8": ["godmother"], "8.3 26.5 4.3": ["gunslinger"], "11.2 13.1 4.7": ["dismemberment"], "-0.5 16.3 -1.0": ["misperceptions"], "6.5 20.1 15.5": ["guilds"], "0.7 9.4 4.9": ["muzzled"], "17.8 1.2 16.1": ["kitschy"], "-7.7 5.7 7.5": ["transceivers"], "2.7 7.2 18.0": ["tint"], "21.2 8.9 2.4": ["anticompetitive"], "6.3 -1.0 4.2": ["itinerant"], "-4.8 9.3 13.4": ["kimberlite"], "-0.5 2.8 -5.5": ["interfacing"], "11.8 1.3 6.2": ["drifter"], "10.3 6.0 1.6": ["nozzles"], "-9.4 28.7 7.7": ["warfighter"], "-10.8 0.3 1.9": ["exhumation"], "8.5 12.5 -0.1": ["radiate"], "0.7 7.6 5.4": ["introverted"], "-4.2 12.9 3.5": ["headstrong"], "-7.0 7.0 -4.1": ["commendations"], "12.6 2.8 1.0": ["buggies"], "1.2 44.4 12.2": ["gunners"], "5.8 2.7 13.6": ["carwash"], "-0.3 0.6 3.8": ["augments"], "9.2 7.1 29.1": ["sauerkraut"], "-5.0 4.7 -0.8": ["sequestration"], "1.7 0.7 1.9": ["tightlipped"], "-6.6 19.6 -2.0": ["indoctrinated"], "7.6 11.5 4.7": ["likeliest"], "1.9 11.7 3.2": ["alludes"], "8.6 3.8 7.5": ["dunno"], "-11.5 5.7 1.6": ["yeshiva"], "-2.4 -2.9 3.4": ["francophone"], "2.6 -0.4 19.4": ["parchment"], "14.6 7.0 5.1": ["forecourt"], "4.9 16.4 12.5": ["idiom"], "-5.0 3.6 9.4": ["fi"], "5.7 13.4 3.3": ["staircases"], "4.3 0.0 18.1": ["furs"], "6.6 28.4 8.8": ["militaristic"], "15.6 4.6 4.2": ["beckon"], "4.7 2.9 2.1": ["guestrooms"], "8.1 5.7 3.6": ["erases"], "7.4 -1.0 6.2": ["ruffle"], "-4.8 16.7 7.9": ["remoteness"], "1.7 0.4 -1.2": ["inverters"], "2.8 16.3 10.0": ["elitism"], "-12.9 2.7 10.3": ["cfs"], "3.9 5.6 12.9": ["slag"], "7.8 5.7 -1.8": ["inundating"], "10.5 7.6 9.3": ["enmeshed"], "16.6 0.4 -1.5": ["divestments"], "7.2 14.0 8.2": ["thuggery"], "-1.4 3.4 6.8": ["workbook"], "8.8 -3.1 2.6": ["repackaging"], "19.3 6.3 13.3": ["cutesy"], "5.1 8.8 9.1": ["gravestones"], "6.2 2.2 1.3": ["copiers"], "9.7 14.0 3.6": ["indisputably"], "-2.8 7.5 15.1": ["gemstones"], "0.0 4.4 4.2": ["carriageway"], "1.3 10.3 8.0": ["tomboy"], "6.1 8.5 12.7": ["fallow"], "6.8 4.4 14.0": ["garland"], "14.5 4.9 12.0": ["mishmash"], "-2.3 9.8 1.9": ["dispassionate"], "1.2 9.0 3.4": ["fluently"], "11.0 5.1 10.4": ["brightens"], "10.3 2.9 -2.0": ["licensor"], "-2.0 2.7 1.2": ["urinary"], "-0.3 6.9 5.1": ["urination"], "8.1 1.6 1.1": ["enshrine"], "7.2 4.6 33.6": ["arugula"], "9.8 12.0 10.0": ["crudely"], "-10.2 10.2 9.8": ["chastity"], "14.8 11.0 22.6": ["specks"], "10.3 9.8 11.0": ["crowing"], "12.7 11.6 4.5": ["jolting"], "11.6 20.5 22.1": ["baited"], "-9.9 16.2 -0.0": ["draftees"], "2.6 4.4 2.0": ["doings"], "12.3 3.3 13.4": ["christening"], "11.7 8.0 15.0": ["redhead"], "-4.0 7.6 1.9": ["linguists"], "12.6 0.1 3.4": ["wafting"], "-1.7 4.9 11.1": ["greenway"], "19.4 23.1 11.8": ["oligarchy"], "5.0 11.8 8.7": ["congregating"], "7.5 18.7 4.6": ["forewarned"], "5.6 0.8 5.6": ["massaged"], "-0.3 -8.6 5.3": ["bursaries"], "2.0 17.0 0.2": ["injurious"], "8.7 18.1 6.9": ["rotors"], "1.1 7.6 1.2": ["footfall"], "3.3 6.0 18.2": ["kayaker"], "22.6 9.0 10.9": ["voila"], "-7.9 1.1 4.6": ["codecs"], "-1.1 8.9 -0.6": ["thoughtfulness"], "-0.0 1.6 8.3": ["codeine"], "-2.0 0.9 8.2": ["milliliters"], "6.5 3.0 5.2": ["anticlimactic"], "-9.4 1.8 2.3": ["moneys"], "2.9 1.4 -2.5": ["slideshows"], "4.9 10.3 14.4": ["butchering"], "15.5 7.3 6.2": ["windswept"], "1.4 5.4 24.1": ["margarita"], "23.1 23.3 9.1": ["encircling"], "-8.7 0.1 8.8": ["treasurers"], "15.7 12.7 9.8": ["whirlpool"], "9.1 6.4 10.4": ["deformities"], "12.2 -0.2 24.8": ["ruby"], "10.3 15.4 -5.1": ["crusades"], "3.6 3.9 4.8": ["minuses"], "-2.5 3.0 3.5": ["critiqued"], "17.4 9.0 12.9": ["spire"], "10.0 15.1 9.5": ["treads"], "1.8 12.3 -0.9": ["incompatibility"], "24.0 -1.2 10.3": ["wunderkind"], "6.7 6.8 0.9": ["regenerative"], "9.3 6.6 10.5": ["splendidly"], "15.2 5.3 3.1": ["swamping"], "-6.2 36.6 6.2": ["firefights"], "4.5 12.0 2.1": ["unsound"], "17.2 8.8 16.3": ["pretzel"], "6.6 -1.6 6.6": ["soaks"], "5.0 20.6 -5.6": ["denigrating"], "19.8 20.9 11.3": ["android"], "-5.1 7.8 4.5": ["generalize"], "6.5 6.3 39.2": ["fennel"], "6.4 1.8 6.5": ["schoolteachers"], "11.1 6.9 7.8": ["cascades"], "23.2 21.7 23.5": ["ravenous"], "-1.6 7.5 10.2": ["bicker"], "5.5 0.4 11.4": ["nativity"], "-0.9 13.3 11.4": ["costar", "transgenes"], "8.7 5.3 10.6": ["bandstand"], "17.1 20.6 3.7": ["zap"], "0.2 8.2 24.3": ["nutmeg"], "-7.7 12.8 3.1": ["subordination"], "4.2 5.3 10.1": ["switchgrass"], "-6.6 17.5 4.7": ["faithfulness"], "12.2 10.6 6.9": ["phoney"], "7.4 10.9 23.5": ["yang"], "-4.9 0.4 -0.3": ["fundraise"], "10.8 8.2 6.7": ["pried"], "-0.5 11.9 12.3": ["geochemical"], "-6.3 5.4 -0.2": ["deputed"], "-3.6 4.8 1.4": ["placekicker"], "14.4 1.7 9.2": ["fizz"], "18.6 11.5 15.1": ["pointy"], "-0.5 7.7 3.5": ["homestretch"], "-8.5 12.5 3.5": ["estrangement"], "1.1 2.5 9.3": ["hospices"], "-10.7 -10.3 1.0": ["residencies"], "2.0 3.6 17.4": ["eyelashes"], "13.8 11.2 3.7": ["cranny"], "5.1 18.8 23.2": ["crossbow"], "5.0 4.1 11.2": ["lipids"], "3.7 10.2 17.3": ["fawn"], "-3.4 17.0 1.5": ["deduce"], "9.1 15.3 29.3": ["acorns"], "13.1 12.8 6.3": ["righting"], "5.6 6.5 -0.3": ["sterilize"], "1.6 -2.1 17.0": ["asides"], "9.3 15.0 5.8": ["shrieks"], "15.0 -1.3 30.5": ["lard"], "9.5 18.6 11.2": ["protestor"], "14.9 18.4 13.4": ["meme"], "4.0 1.6 16.3": ["pendants"], "17.0 5.8 20.6": ["finicky"], "21.5 10.9 10.5": ["detritus"], "17.5 2.2 8.3": ["cutouts"], "22.8 5.2 12.2": ["hamsters"], "-1.4 26.1 6.0": ["unilateralism"], "14.3 -2.6 4.3": ["underwhelmed"], "0.7 5.1 2.9": ["goer"], "10.2 -2.5 1.9": ["wove"], "5.3 12.0 7.8": ["synapses"], "1.9 5.4 8.7": ["occasioned"], "-2.8 21.9 6.3": ["observable"], "3.9 8.4 11.8": ["inoculated"], "19.9 -1.0 15.8": ["greased"], "9.0 6.2 -0.1": ["notepad"], "3.8 7.5 23.7": ["scones"], "-0.9 -2.5 46.4": ["tilapia"], "16.3 25.1 6.7": ["frightful"], "7.8 4.7 14.2": ["sunbathing"], "-3.9 4.0 34.8": ["mutton"], "3.3 8.5 3.3": ["floorboards"], "16.0 12.2 11.6": ["clumsily"], "6.7 -0.7 22.5": ["jute"], "14.5 3.4 5.2": ["oodles"], "10.3 11.4 8.7": ["lass"], "7.2 5.9 27.0": ["songbirds"], "17.4 12.1 6.8": ["whizzing"], "5.7 19.1 8.1": ["foiling"], "4.9 9.9 -2.8": ["debunking"], "-1.9 3.1 3.3": ["urologist"], "-0.6 10.4 -3.0": ["defaming"], "4.9 2.0 14.8": ["youtube"], "0.7 19.2 6.8": ["overconfidence"], "1.4 23.1 3.9": ["repress"], "-4.3 3.4 13.5": ["snowmelt"], "7.7 1.0 10.8": ["paleontologist"], "0.5 2.0 -0.5": ["reconfirmed"], "10.7 7.9 12.6": ["flummoxed"], "7.4 15.4 2.8": ["jeering"], "5.3 2.1 9.9": ["unaltered"], "1.4 0.9 3.9": ["uncollected"], "-6.0 1.4 1.8": ["disqualifying"], "22.5 9.7 32.5": ["seagulls"], "-3.2 -0.3 2.2": ["rescission"], "1.0 8.3 9.9": ["tha"], "5.2 13.8 4.9": ["blameless"], "9.2 5.1 3.4": ["midwest"], "13.3 1.0 11.4": ["gongs"], "14.1 9.3 10.0": ["blondes"], "17.0 17.7 10.3": ["quiver"], "8.0 5.6 11.0": ["fedora"], "4.6 0.2 5.7": ["spoofs"], "10.3 7.4 13.2": ["horny"], "12.0 5.7 -0.3": ["flogged"], "15.5 6.2 10.3": ["stockmarket"], "-7.1 0.8 2.3": ["runaways"], "6.0 0.7 18.9": ["applesauce"], "1.8 11.2 -2.1": ["critiquing"], "18.3 5.0 1.6": ["barcodes"], "8.4 0.4 11.0": ["raceway"], "3.6 3.6 8.9": ["pithy"], "-6.6 10.5 7.9": ["immigrate"], "-7.7 6.2 50.4": ["coho"], "8.7 -3.8 3.4": ["outgrew"], "2.0 -0.2 1.1": ["infuses"], "3.9 40.9 3.5": ["jihadis"], "-8.7 6.7 -0.9": ["excommunicated"], "4.0 0.5 5.0": ["hkd"], "14.2 2.6 11.5": ["slicker"], "-2.0 7.8 9.0": ["uninhibited", "takas"], "14.5 3.6 6.8": ["clambered"], "12.5 3.3 7.5": ["masterclass"], "-3.8 4.9 4.0": ["reprises"], "14.7 5.3 -6.3": ["multifunctional"], "8.1 2.5 16.3": ["dumpsters"], "1.3 6.9 11.0": ["fluffed"], "1.1 17.3 4.0": ["expediency"], "5.6 8.8 6.8": ["flipside"], "7.5 5.7 14.5": ["toasts"], "10.7 0.9 17.0": ["parlors"], "8.4 12.0 11.8": ["classically"], "13.4 6.6 17.8": ["confection"], "5.9 4.7 -6.0": ["amalgamated"], "3.3 3.3 -0.3": ["exuded"], "-1.9 1.9 8.0": ["piercings"], "1.8 20.0 11.5": ["malignancy"], "-7.8 10.0 -4.5": ["ministering"], "-3.6 12.9 3.3": ["madrassas"], "6.5 7.3 7.8": ["weightlessness"], "9.9 2.6 12.0": ["frisky"], "21.1 9.9 14.0": ["lurching"], "13.9 3.9 -0.7": ["ultrasonic"], "16.4 7.0 26.7": ["beached"], "-2.2 5.0 7.3": ["broach"], "5.8 2.0 5.4": ["multiethnic"], "4.4 6.4 8.4": ["helmer"], "5.9 12.9 6.2": ["gusty"], "2.0 0.6 10.8": ["chartering"], "5.8 6.5 9.8": ["foaming"], "-3.0 7.6 8.2": ["narrating"], "-0.6 9.1 4.5": ["outpatients"], "5.5 11.2 4.3": ["abides"], "3.5 10.5 11.4": ["scalpers"], "-2.0 0.7 -2.4": ["pertained"], "15.8 5.2 7.2": ["pokes"], "1.6 9.8 8.6": ["playfulness"], "3.0 5.6 4.7": ["lapel"], "3.9 7.8 9.7": ["charmer"], "9.4 9.8 -0.5": ["bulldoze"], "-4.2 10.1 3.1": ["curative"], "-2.7 -1.7 8.8": ["sociologists"], "15.7 -0.4 12.7": ["portly"], "-7.5 7.5 12.2": ["forceout"], "-2.3 8.4 11.1": ["clowning"], "2.0 5.3 10.7": ["midmarket"], "-7.6 10.0 12.7": ["laity"], "4.3 1.3 -5.3": ["vp"], "9.3 11.9 8.6": ["idiosyncrasies"], "9.8 3.0 9.3": ["commercialism"], "13.5 11.3 11.7": ["decelerating"], "1.6 9.8 7.1": ["barista"], "0.9 9.2 4.7": ["paperbacks"], "-2.5 12.2 2.1": ["insinuations"], "1.1 8.8 8.8": ["inequitable"], "5.8 3.7 14.0": ["quickfire"], "-0.6 2.7 8.6": ["finales"], "11.7 16.1 -0.2": ["succor"], "5.8 0.9 1.0": ["convergent"], "4.9 1.9 -0.2": ["romps"], "13.0 4.9 3.8": ["hotly"], "11.6 -0.9 1.1": ["encapsulate"], "5.6 5.0 15.5": ["greyhounds"], "0.4 8.0 10.9": ["khakis"], "2.7 -0.7 37.9": ["prosciutto"], "12.3 21.5 7.6": ["colonize"], "1.5 -5.4 2.7": ["trooped"], "9.6 12.3 8.9": ["uncharted"], "13.1 15.6 9.6": ["joyfully"], "12.7 -2.7 3.4": ["ee"], "10.1 8.4 8.1": ["schoolboys"], "12.2 -0.9 0.1": ["cashless"], "4.9 26.5 4.5": ["regiments"], "5.8 1.7 12.2": ["fiddler"], "2.9 5.9 13.2": ["stagehands"], "5.4 6.5 5.1": ["identifier"], "1.5 7.4 -0.5": ["soluble"], "-3.5 -1.9 13.1": ["blazers"], "14.2 3.1 12.0": ["ooze"], "-12.0 3.8 13.7": ["spaying"], "-4.2 6.9 0.6": ["interoperate"], "3.5 16.4 6.2": ["exacted"], "-7.8 7.7 -0.9": ["reprimands"], "-2.2 6.7 -1.4": ["exoneration"], "16.1 15.4 17.8": ["officialdom"], "8.0 6.6 2.2": ["prelate"], "-5.3 7.5 27.0": ["brisket"], "8.1 9.2 28.9": ["bobcat"], "4.2 8.6 0.3": ["nauseous"], "9.1 2.3 8.0": ["lithe"], "-4.3 9.0 5.2": ["demobilization"], "13.3 3.3 2.1": ["moxie"], "13.4 21.8 9.9": ["polluter"], "2.9 7.6 5.4": ["banishment"], "5.3 2.1 -0.7": ["outperforms"], "-3.2 5.6 4.5": ["presets"], "3.1 7.7 10.1": ["aerials"], "5.5 3.5 11.6": ["subcontracting"], "2.5 0.6 4.1": ["pamper"], "-8.1 4.6 5.1": ["vol"], "-2.8 8.0 2.1": ["bookshops"], "4.4 29.6 10.6": ["crouch"], "11.3 5.5 14.2": ["handfuls"], "28.0 16.3 33.3": ["marshmallow"], "3.6 23.8 9.0": ["sharpshooters"], "3.3 10.3 0.6": ["murmur"], "10.5 13.2 8.9": ["swaggering"], "9.4 20.5 6.3": ["manipulates"], "2.8 3.2 3.5": ["insolvencies"], "5.4 -2.3 8.6": ["jumpsuits"], "3.9 3.6 3.3": ["tastefully"], "14.5 8.4 4.5": ["snatches"], "-0.9 9.7 7.2": ["incompletions", "rowdyism"], "9.2 2.7 -0.4": ["contravene"], "1.3 7.2 -4.2": ["disproved"], "21.9 1.3 5.1": ["saleswoman"], "5.9 0.8 15.5": ["shoestring"], "-6.3 5.0 30.3": ["turmeric"], "11.1 8.8 0.7": ["rampaged"], "-3.0 9.8 6.9": ["institutionalize"], "-0.2 15.1 7.1": ["southerly"], "-0.9 7.3 12.3": ["sardonic"], "14.6 7.9 8.0": ["gibberish"], "-4.3 0.1 7.9": ["choosy"], "-6.9 34.0 3.4": ["warfighters"], "17.4 15.4 10.6": ["vandal"], "-0.6 11.3 1.0": ["replaceable"], "4.5 7.7 0.5": ["bloodstained"], "3.3 5.5 3.5": ["rifling"], "-5.1 8.1 7.7": ["demerits"], "7.9 7.2 9.1": ["prairies"], "0.5 4.9 3.4": ["abdicated"], "3.5 8.2 37.4": ["beet"], "3.1 9.3 8.1": ["sappy"], "10.6 13.2 4.2": ["stuntman"], "6.9 3.9 7.5": ["foreshadow"], "-6.5 11.1 17.4": ["changeups"], "-8.8 -1.3 8.9": ["restorations"], "-3.3 7.5 9.4": ["lyricism"], "0.7 2.7 6.1": ["junket"], "0.2 17.5 11.6": ["politeness"], "17.8 4.5 3.1": ["coursing"], "4.4 7.7 6.3": ["preteen"], "13.4 12.3 15.3": ["underfoot"], "3.2 1.0 11.2": ["photonics"], "-3.0 12.1 15.5": ["curveballs"], "9.2 18.1 -7.0": ["purifying"], "-0.4 0.5 6.8": ["geotechnical"], "5.9 -3.4 18.4": ["surfboards"], "22.6 6.6 14.7": ["cornucopia"], "5.6 8.7 4.6": ["recesses"], "-5.8 12.2 7.4": ["tradeoffs"], "11.2 4.1 1.3": ["reverberating"], "-1.4 13.6 18.8": ["shipboard"], "-2.0 13.3 8.9": ["reenactment"], "18.4 6.4 8.9": ["beater"], "-3.4 -1.3 1.4": ["unrated"], "6.3 13.3 2.3": ["prefix"], "8.3 14.5 11.8": ["scavengers"], "0.8 16.1 9.8": ["gotcha"], "0.6 8.7 3.2": ["pasts"], "4.9 7.6 7.8": ["auteur"], "3.1 8.1 1.6": ["indenture"], "0.4 8.0 11.1": ["salvageable"], "10.1 5.5 8.0": ["downcast"], "3.2 9.9 13.6": ["patter"], "8.0 2.7 -1.9": ["turnoff"], "-1.6 9.3 3.0": ["deferential"], "11.3 3.2 6.1": ["melded"], "3.5 2.9 47.5": ["anchovies"], "-3.2 5.7 -2.6": ["inculcate"], "24.4 6.7 4.4": ["billionth"], "11.4 19.2 9.1": ["impostor"], "11.4 10.8 29.6": ["shipbuilders"], "4.3 15.2 7.7": ["hecklers"], "15.2 24.6 16.6": ["gladiator"], "1.1 14.6 11.1": ["frustratingly"], "6.3 2.3 10.4": ["showtime"], "-4.7 3.2 0.5": ["gazetted"], "9.8 2.5 1.0": ["wristwatch"], "7.6 10.0 0.7": ["radiated"], "5.7 2.9 5.8": ["outpaces"], "-2.3 4.6 1.6": ["frequenting"], "2.2 12.1 11.6": ["descendents"], "4.2 13.6 2.5": ["counterfeits"], "9.8 9.2 2.7": ["sleepwalking"], "3.7 15.6 3.5": ["pallbearers"], "-10.9 14.5 19.1": ["groundballs"], "3.8 18.1 11.7": ["lawman"], "-6.0 7.7 1.8": ["soonest"], "-2.1 2.3 15.8": ["ecotourism"], "12.0 14.4 12.1": ["chainsaws"], "12.5 -4.5 10.2": ["ritzy"], "14.8 9.7 5.2": ["unloved"], "-1.1 17.4 4.2": ["belittling"], "7.4 5.9 2.0": ["actuaries"], "27.9 10.9 13.0": ["spherical"], "6.1 5.4 21.3": ["cadaver"], "17.5 16.1 17.3": ["scarecrow"], "4.9 8.7 16.8": ["transplanting"], "14.1 11.0 10.0": ["overlaid"], "11.1 7.7 7.1": ["reclining"], "-5.9 1.7 10.8": ["bloodlines"], "15.3 16.3 10.7": ["alchemy"], "8.8 16.1 14.1": ["ashtray"], "9.9 10.3 20.3": ["cheeseburgers"], "5.9 7.7 5.0": ["scoffs"], "9.6 9.4 9.0": ["dumber"], "-1.2 19.1 46.8": ["inshore"], "13.4 13.3 12.4": ["twitching"], "-4.5 -3.1 11.2": ["saris"], "4.7 16.9 8.7": ["neuron"], "2.6 5.5 12.5": ["rhyming"], "0.2 8.3 5.6": ["deters"], "6.0 -0.3 3.7": ["paydirt"], "21.3 18.8 15.2": ["webs"], "11.3 15.2 17.7": ["mitts"], "-5.3 7.3 -0.2": ["neurologists"], "10.2 3.0 6.1": ["implanting"], "10.8 4.6 2.8": ["niggling"], "3.4 7.2 13.8": ["gypsum"], "0.1 4.8 8.8": ["enacts"], "12.9 12.1 -2.3": ["detonator"], "-0.9 5.3 14.9": ["sparklers"], "14.3 13.5 12.6": ["bleep"], "-1.3 1.8 0.6": ["chancellors"], "5.5 9.7 12.5": ["prognosticators"], "-0.4 5.5 9.4": ["panchayats"], "2.0 3.3 4.8": ["sloppiness"], "-2.7 5.0 5.8": ["unsubscribe"], "-6.6 1.7 6.1": ["colonoscopies"], "6.5 6.6 -2.4": ["consign"], "-1.6 19.2 4.1": ["leaderships"], "5.8 8.8 10.9": ["petting"], "-6.0 1.2 -3.3": ["sensitization"], "2.3 7.8 27.3": ["cornbread"], "2.4 5.2 0.1": ["presidencies"], "-4.6 7.9 0.8": ["ebooks"], "4.9 1.1 9.2": ["holdups"], "1.5 5.2 2.0": ["textual"], "10.7 18.4 7.4": ["barrages"], "4.0 6.5 23.1": ["sandbar"], "16.9 24.8 7.1": ["maniacal"], "9.3 6.0 6.4": ["bashes", "ropeway"], "2.1 12.2 13.4": ["ki"], "0.7 8.4 13.3": ["disablement"], "7.5 13.5 1.1": ["stairwells"], "2.4 8.0 29.9": ["vinaigrette"], "9.4 -3.8 2.2": ["predated"], "7.5 11.2 5.9": ["friendliest"], "8.9 17.5 9.4": ["diehards"], "8.5 7.5 0.3": ["seperate"], "2.9 -0.2 4.2": ["ms"], "1.1 16.3 -1.2": ["vilification"], "-1.4 -0.4 -11.9": ["analyzers"], "-0.8 11.5 18.3": ["sows"], "-9.3 -0.4 -0.0": ["postoperative"], "5.8 15.6 7.5": ["uninteresting"], "-3.9 7.1 4.6": ["dislocations"], "0.3 15.0 15.7": ["politico"], "2.7 3.7 5.1": ["fourteenth"], "3.6 21.7 6.0": ["questioners"], "3.2 4.6 5.1": ["jaundice"], "0.8 10.7 8.0": ["abundantly"], "12.0 0.2 12.3": ["windfalls"], "3.7 6.7 13.0": ["moonshine"], "9.7 17.4 13.1": ["pillaging"], "-6.2 -2.6 3.1": ["workgroup"], "4.0 16.5 -4.4": ["renouncing"], "3.1 6.3 8.1": ["turntables"], "-3.7 0.7 -2.8": ["photocopies"], "0.6 4.8 1.5": ["sensitively"], "2.6 8.9 3.7": ["unifies"], "7.3 11.8 26.7": ["flippers"], "12.6 20.5 18.9": ["spineless"], "16.3 6.9 18.3": ["dung"], "12.1 10.3 17.2": ["chariot"], "18.1 8.7 8.2": ["peddlers"], "1.2 -2.2 0.1": ["presentable"], "-0.9 5.3 6.4": ["urbane"], "14.5 8.2 3.4": ["wresting"], "3.4 6.1 -0.2": ["hairpin"], "-0.5 8.3 14.2": ["grates"], "8.7 0.1 -2.1": ["microsite"], "8.1 10.9 11.8": ["percussive"], "2.9 1.4 4.9": ["architecturally", "psychodrama"], "13.0 3.2 8.5": ["tempestuous"], "-0.1 10.0 5.5": ["claps"], "13.3 11.1 16.6": ["cheetah"], "11.1 22.0 2.0": ["archrivals"], "13.9 14.7 17.3": ["boomerang"], "3.0 2.8 -0.3": ["malpractices"], "6.8 7.2 3.1": ["understate"], "-4.7 12.2 10.0": ["metastatic"], "16.3 5.0 12.6": ["awnings"], "-3.5 12.4 5.8": ["antibacterial"], "-3.1 7.5 22.8": ["beekeeping"], "-3.4 -3.5 17.2": ["heifer"], "12.1 7.1 1.3": ["swastikas"], "-1.0 1.5 26.4": ["tamales"], "7.2 0.5 4.5": ["balks"], "4.5 12.0 10.7": ["sickest"], "17.5 1.2 12.0": ["breakneck"], "11.2 12.0 9.9": ["genitalia"], "-4.3 3.1 12.6": ["workdays"], "7.4 12.1 6.3": ["awoken"], "11.6 14.2 20.7": ["gimme"], "11.5 11.6 3.5": ["fixer"], "-14.9 6.1 2.5": ["accompanist"], "-0.1 8.8 4.6": ["cliched"], "9.7 4.8 14.2": ["lilac"], "-1.2 12.1 -0.6": ["posits"], "0.8 7.1 -0.4": ["acquiesced"], "1.7 11.7 7.2": ["newscaster"], "-5.4 3.2 4.4": ["vacationed"], "-1.5 1.0 7.6": ["remastered"], "1.1 4.7 -2.4": ["relived"], "3.7 10.0 -2.0": ["counterclaim"], "12.1 5.2 13.6": ["carves"], "-6.0 9.8 2.7": ["ascribe"], "5.2 21.3 5.3": ["janjaweed"], "-6.8 4.8 9.2": ["groundouts"], "10.9 3.6 3.8": ["swooning"], "1.1 5.5 4.7": ["worksheet"], "12.7 7.9 0.0": ["sensationally"], "3.1 10.6 3.1": ["stonewalled"], "24.2 15.4 7.5": ["picturing"], "1.5 26.2 4.9": ["subjugation"], "-0.1 -1.5 6.0": ["moonlighting"], "4.2 4.4 38.6": ["kale"], "-3.6 14.8 6.3": ["disaffection"], "2.9 16.2 10.8": ["lulls"], "14.7 10.8 6.6": ["follies"], "5.0 5.8 4.1": ["checkbooks"], "24.7 2.1 9.1": ["muscling"], "6.8 10.0 16.1": ["pigskin"], "-1.3 7.9 4.4": ["drivetrain"], "7.7 14.9 3.0": ["bearers"], "13.3 11.0 7.5": ["quixotic"], "-7.9 15.5 0.7": ["argumentative"], "1.7 13.6 9.4": ["neoliberal"], "3.2 2.4 6.5": ["hackles"], "1.4 9.8 4.9": ["demonstrative"], "0.8 4.8 2.8": ["rewrites"], "13.7 18.1 10.2": ["crevices"], "9.7 -4.6 16.7": ["snip"], "5.4 4.0 10.5": ["shaves"], "6.0 0.1 13.3": ["doles"], "-5.5 5.0 8.8": ["itemize"], "8.8 12.2 8.2": ["dancefloor"], "1.9 11.1 0.5": ["earplugs"], "9.2 9.4 3.7": ["speedometer"], "0.8 -0.2 11.4": ["divorcee"], "24.7 5.9 17.3": ["fattest"], "7.6 10.0 9.7": ["sculpt"], "0.6 8.0 14.5": ["dyeing"], "-2.8 7.9 0.5": ["untoward"], "-5.8 -3.6 27.9": ["broiler"], "15.2 14.9 3.6": ["ignominious"], "7.1 4.9 6.2": ["hangovers"], "2.5 -1.5 4.9": ["letterman"], "9.6 8.1 4.6": ["soapbox"], "1.8 9.0 7.6": ["refilling"], "8.4 10.5 7.8": ["backwoods"], "1.1 7.4 5.6": ["behooves"], "-2.0 5.2 7.7": ["overstayed"], "12.7 13.4 9.6": ["imitators"], "6.2 -3.4 4.6": ["conformed"], "-0.0 11.4 9.5": ["scold", "inlaws"], "9.3 22.9 7.1": ["backfires"], "10.3 7.3 3.1": ["midcap"], "0.9 9.9 -1.2": ["legitimized"], "5.3 0.4 3.6": ["thumbed"], "-4.7 1.0 5.1": ["opine", "uneventfully"], "16.9 5.9 5.0": ["megastar"], "0.6 19.3 5.5": ["humanist"], "2.7 1.0 17.4": ["prefectures", "pelletized"], "3.3 6.9 7.0": ["dem"], "3.6 12.5 7.9": ["flirts"], "6.4 6.6 -3.3": ["dissipating"], "19.7 5.0 16.4": ["giraffes"], "12.0 5.6 22.4": ["gelatin"], "7.9 17.0 8.2": ["passageway"], "4.5 -3.4 12.9": ["housekeepers"], "0.4 6.9 14.5": ["earring"], "1.2 2.3 11.1": ["midlife"], "10.8 8.9 31.2": ["chopsticks"], "4.4 6.1 2.9": ["wouldnt"], "0.7 11.2 2.4": ["dutiful"], "3.4 0.1 7.5": ["typifies"], "11.3 3.9 14.4": ["frosted"], "8.0 13.3 17.9": ["ironclad"], "4.2 15.1 23.1": ["raptors"], "1.5 9.9 10.1": ["moviemaking"], "4.0 12.1 11.9": ["armpit"], "-0.6 14.0 2.3": ["forcible"], "2.1 8.3 4.1": ["ringer"], "-4.3 -0.2 4.5": ["mailto"], "-5.5 16.8 2.3": ["orator"], "15.3 17.4 7.8": ["breathlessly"], "11.1 21.9 13.8": ["blackness"], "5.3 6.5 23.5": ["foodstuff"], "3.1 8.9 9.6": ["syllables"], "9.6 8.2 -2.8": ["trendsetter"], "8.2 3.5 12.4": ["deconstruction"], "-9.6 0.7 8.2": ["stockists"], "1.8 6.0 16.9": ["riverbed"], "1.3 9.6 8.1": ["overshoot"], "6.3 16.4 3.6": ["infuriate"], "17.1 -0.4 11.6": ["priciest"], "9.1 10.2 4.1": ["imprints"], "10.8 9.0 1.4": ["pram"], "22.1 5.7 4.9": ["backlit"], "17.5 12.4 6.5": ["shitty"], "13.6 17.3 8.1": ["jabbing"], "13.4 -0.9 0.1": ["ceo"], "12.1 4.1 3.0": ["printout"], "8.7 5.2 5.2": ["mashups"], "1.9 10.0 -0.6": ["extorted"], "10.3 3.2 10.6": ["uncorked"], "-0.7 4.0 25.5": ["boathouse"], "7.1 3.7 5.0": ["smoothest"], "10.0 17.3 9.5": ["savagely"], "2.8 3.8 -3.6": ["auditoriums"], "11.7 -3.5 13.2": ["suspenders"], "-1.3 1.0 4.7": ["swabs"], "7.2 14.9 15.4": ["ruefully"], "-1.4 8.4 19.1": ["bakes"], "0.2 12.1 4.9": ["wearers"], "6.7 -0.9 16.4": ["granola"], "10.9 6.9 -0.8": ["unfashionable"], "9.4 6.8 8.7": ["faeces"], "5.3 16.7 4.3": ["irrefutable"], "-2.2 7.4 10.9": ["overclocking"], "0.9 14.8 2.5": ["teleprompter"], "12.5 5.6 4.7": ["rupturing"], "-9.0 -1.9 16.1": ["progesterone"], "4.7 11.0 10.7": ["mantel"], "3.1 0.0 3.9": ["conceiving"], "-1.2 9.1 19.5": ["musher"], "8.7 10.7 10.0": ["servitude"], "1.0 6.6 -0.2": ["scrupulous"], "3.6 7.7 4.5": ["mods"], "4.6 -0.6 -2.2": ["barnstorming"], "-5.0 14.7 4.4": ["instigation"], "9.3 22.3 10.9": ["cybercriminals"], "5.7 5.2 11.0": ["ferment"], "-7.9 6.6 -0.1": ["altercations"], "-1.3 9.0 -5.7": ["insinuated"], "1.7 2.6 -2.0": ["smooths"], "10.2 13.5 8.7": ["lonesome"], "-3.2 6.9 4.0": ["bop"], "-1.1 8.7 8.7": ["leaguers"], "11.8 3.6 9.3": ["sop"], "13.8 12.0 13.6": ["stragglers"], "0.6 10.5 28.3": ["trappers"], "14.9 17.0 22.2": ["weasel"], "-7.0 12.1 2.0": ["closeted"], "6.6 14.8 8.9": ["sheiks"], "1.2 9.9 3.5": ["microscopy"], "-7.5 2.8 0.2": ["promulgation"], "4.4 11.6 2.1": ["hastening"], "13.7 13.6 9.6": ["townsfolk"], "2.8 10.3 9.0": ["aimless"], "1.7 4.0 12.7": ["repainting"], "3.9 11.3 31.1": ["pounders"], "-4.4 10.9 7.5": ["rebounders"], "15.8 8.4 14.5": ["sultan"], "-2.4 -1.9 12.1": ["crochet"], "4.2 1.7 12.9": ["skimp"], "-8.8 0.8 9.9": ["opioid"], "-3.6 5.2 4.1": ["voicemails"], "0.1 10.8 5.8": ["yds"], "6.5 4.6 3.5": ["unravels"], "2.4 2.0 6.7": ["undergrad"], "-3.0 15.7 -0.1": ["leftwing"], "3.5 8.4 5.6": ["gypsies"], "5.9 11.9 3.9": ["chastened"], "12.1 0.7 4.7": ["spurning"], "8.9 12.7 -3.2": ["democratize"], "13.1 2.0 10.8": ["tinsel"], "1.3 6.4 12.8": ["unsanitary"], "23.6 11.6 4.9": ["monopolistic"], "4.8 10.5 8.3": ["fantasize"], "2.0 12.9 7.6": ["subverting"], "4.8 12.9 3.2": ["pestering"], "14.6 18.5 21.8": ["leeches"], "4.8 13.9 19.9": ["frigates"], "-0.2 10.0 2.0": ["individualistic"], "17.0 -3.1 0.8": ["relaunching"], "2.0 0.1 -2.6": ["formalizing"], "12.5 7.9 20.3": ["reddish"], "1.5 11.3 3.1": ["rile"], "5.7 7.0 -2.6": ["reinvigorating"], "14.1 11.5 9.5": ["vestige"], "6.9 4.3 11.2": ["hyperextended"], "-9.6 -3.4 5.4": ["retested"], "10.8 10.8 3.4": ["decibel"], "10.5 2.3 2.2": ["dustup"], "5.3 11.3 3.4": ["gassing"], "13.1 5.9 16.7": ["teapot"], "7.0 4.0 10.4": ["homering"], "5.0 24.8 -4.4": ["vilify"], "3.6 9.3 8.8": ["irradiation"], "0.4 11.6 10.2": ["crisply"], "6.7 11.2 7.1": ["nastier"], "15.5 16.4 8.2": ["blindfold"], "0.5 0.2 1.6": ["cogeneration"], "1.1 19.5 6.0": ["blinders"], "-12.3 9.5 11.9": ["homeschooling"], "-1.5 4.6 17.3": ["distillate"], "13.0 -1.3 7.3": ["homespun"], "-3.9 9.3 1.5": ["breakouts"], "-1.5 15.3 21.2": ["shipwrecks"], "10.7 17.7 7.7": ["nastiest"], "-6.1 9.1 7.0": ["pullbacks"], "12.7 -4.2 -0.6": ["meandered"], "-3.9 5.2 10.0": ["nonresidential"], "-6.2 5.6 6.8": ["failover"], "-0.0 7.9 0.4": ["scrupulously"], "-3.7 7.3 7.7": ["foreclosing"], "-1.3 6.5 11.5": ["rarities"], "8.3 9.6 24.5": ["blackberries"], "19.6 6.0 15.2": ["wonky"], "3.5 23.8 -0.2": ["bellicose"], "2.5 6.4 0.8": ["fathering"], "3.3 -0.8 -5.3": ["repute"], "11.1 1.3 10.3": ["shindig"], "2.7 2.3 1.0": ["bhp"], "-0.1 11.0 -1.7": ["communicative"], "-1.8 4.8 1.1": ["plagiarized"], "8.7 4.3 11.0": ["lattes"], "-5.2 19.6 -0.6": ["publics"], "17.0 8.1 13.4": ["crayon"], "-7.5 11.4 2.7": ["denominational"], "0.5 3.7 5.9": ["recordkeeping"], "-3.7 12.9 3.5": ["harshness"], "-5.9 1.5 -3.6": ["readmitted"], "-3.3 -4.6 6.9": ["hirings"], "-0.1 5.6 7.3": ["mitigates"], "8.4 11.4 11.4": ["sulking"], "1.3 18.7 2.5": ["apostle"], "13.7 18.0 6.1": ["idly"], "5.3 21.0 10.4": ["meteors"], "10.4 -3.8 5.6": ["flatbed"], "3.9 8.3 7.2": ["bullishness"], "4.9 11.5 22.4": ["evergreens"], "-1.2 13.4 2.0": ["earpiece"], "2.0 11.6 0.3": ["frisked"], "-2.9 1.0 -3.4": ["acquaint"], "10.5 8.2 7.9": ["spindle"], "15.3 4.5 2.7": ["deregulate"], "-5.8 4.6 0.6": ["imparts"], "-3.1 18.4 6.2": ["secularist"], "-0.9 8.4 16.0": ["angiogenesis"], "9.9 15.8 11.4": ["constellations"], "3.8 4.3 4.0": ["retinal"], "-0.2 10.8 16.8": ["stilted"], "1.5 8.2 4.7": ["mysticism"], "-3.4 10.5 6.5": ["intercede"], "12.8 7.6 14.2": ["preening"], "3.6 1.1 11.6": ["boozing"], "-5.9 4.5 -1.5": ["polygamous"], "6.6 13.2 12.8": ["machismo"], "-1.6 20.6 7.3": ["multilateralism"], "4.3 6.3 1.8": ["upstanding"], "4.1 20.6 -0.8": ["stationing"], "-9.2 1.1 9.4": ["labrum"], "6.1 4.1 6.4": ["slogged"], "10.8 8.9 18.6": ["spoonful"], "2.6 8.6 0.5": ["dearer"], "-5.0 2.7 10.8": ["cohabitation"], "6.2 0.0 13.1": ["partaking"], "16.3 28.1 -1.8": ["repelling"], "6.9 16.5 3.0": ["narco"], "-0.7 -1.3 4.1": ["ne"], "-8.6 5.7 -2.7": ["unreserved"], "2.6 12.4 10.3": ["invective"], "-1.0 17.2 11.1": ["prerogatives"], "9.0 22.7 5.2": ["deceptions"], "6.4 7.0 3.6": ["minimalism"], "19.7 10.5 2.7": ["duopoly"], "4.9 3.4 2.9": ["waists"], "14.7 10.2 8.8": ["slinky"], "11.5 2.0 0.6": ["multifunction"], "10.7 11.8 17.2": ["whiskers"], "10.1 4.2 2.1": ["waltzed"], "10.8 12.2 5.1": ["drudgery"], "4.5 16.0 3.7": ["ringleaders"], "-1.3 -1.2 1.4": ["rambled"], "21.9 11.2 12.2": ["molten"], "7.9 0.2 2.4": ["gee"], "6.2 14.7 9.9": ["nuclei"], "2.0 9.9 1.2": ["exasperating"], "1.2 7.3 17.0": ["snowshoes"], "10.6 19.4 7.7": ["dodges"], "8.7 7.9 -0.9": ["cahoots"], "10.6 16.8 13.9": ["gales"], "6.5 6.3 9.6": ["preliminarily"], "7.3 17.6 17.2": ["sandbag"], "-0.0 6.4 4.8": ["hoarded"], "4.8 11.2 -2.3": ["entrapped"], "8.6 13.7 4.8": ["regenerating"], "5.7 1.4 -1.2": ["identifiers"], "12.2 9.2 26.2": ["scrumptious"], "0.2 14.7 14.9": ["outcrop"], "21.5 12.4 5.2": ["swoops"], "15.2 15.7 2.5": ["overtakes"], "7.9 18.2 10.3": ["approximation"], "1.9 1.8 16.8": ["braided"], "7.8 4.8 5.4": ["extrapolated"], "14.2 14.2 8.5": ["whiteboard"], "0.2 19.4 7.7": ["micromanage"], "9.4 19.3 21.0": ["mites"], "5.1 10.9 4.2": ["retrained"], "7.5 -0.3 0.5": ["mailroom"], "3.0 7.3 6.0": ["sowed"], "17.9 16.8 19.6": ["digger"], "13.6 13.6 6.0": ["bankrupting"], "-7.4 25.7 6.7": ["marksmanship"], "-3.1 9.0 1.7": ["impairing"], "11.8 0.8 17.5": ["packer"], "2.3 23.3 7.0": ["inhumanity"], "19.1 6.7 52.1": ["eels"], "23.0 13.7 8.7": ["moveable"], "8.5 13.6 8.0": ["crackle"], "14.2 14.3 4.8": ["sieve"], "8.3 1.9 16.5": ["soya"], "12.3 6.8 -0.0": ["lambasting"], "7.2 12.7 2.2": ["deciphering"], "13.5 14.2 6.4": ["bellowing"], "20.2 6.0 16.8": ["scrawny"], "7.1 3.3 7.3": ["stuttered"], "-0.3 2.0 3.2": ["earbuds"], "20.8 15.8 14.4": ["spaceships"], "12.9 5.3 7.8": ["draping"], "-2.7 9.5 6.6": ["disinfecting"], "-3.4 6.8 7.3": ["weeded", "heterodimers"], "19.0 6.5 18.3": ["gobs"], "6.4 22.0 2.9": ["nuisances"], "6.0 12.1 4.5": ["clenched"], "15.4 24.0 12.5": ["werewolves"], "10.1 13.2 8.3": ["cogs"], "5.5 15.1 3.2": ["deformation"], "-1.5 32.2 12.9": ["armament"], "8.7 24.4 4.6": ["militarized"], "13.9 7.8 21.0": ["skewer"], "-1.1 6.8 1.5": ["evicting"], "-0.4 4.3 24.7": ["roasts"], "7.8 14.3 8.7": ["dev"], "11.7 0.7 16.0": ["madcap"], "10.1 0.1 18.0": ["fixings"], "5.5 4.6 -0.2": ["entitling"], "19.8 8.8 16.1": ["inflatables"], "3.6 7.9 3.6": ["backsliding"], "0.4 10.6 6.3": ["disembarked"], "22.2 0.9 4.4": ["honchos"], "15.3 0.6 2.8": ["shakeout"], "-0.5 17.7 10.0": ["unapologetically"], "17.0 2.9 4.4": ["novelties"], "11.0 12.8 19.6": ["mitt"], "5.9 3.9 4.9": ["cajoled"], "-1.5 1.6 14.5": ["beading"], "6.0 14.3 2.3": ["assiduously"], "0.3 10.1 0.6": ["leaguer"], "4.4 13.8 6.6": ["brinkmanship"], "8.5 19.1 4.1": ["jugular"], "9.6 -0.0 9.7": ["tamer"], "3.5 19.3 9.3": ["amoral"], "6.9 15.0 13.8": ["ricochet"], "12.4 -0.7 2.6": ["wafted"], "4.5 4.9 18.2": ["mustaches"], "12.3 18.8 5.9": ["forsaken"], "3.7 8.7 6.8": ["strumming"], "1.8 7.6 9.3": ["amplitude"], "-1.3 11.9 7.6": ["incapacity"], "7.2 3.0 17.8": ["kilt"], "6.9 15.5 19.2": ["leopards"], "12.3 5.8 18.5": ["nested"], "12.1 3.4 7.3": ["fasten"], "-1.1 7.2 0.8": ["polonium"], "10.2 9.2 7.3": ["squeal"], "2.0 3.9 1.3": ["captioned"], "9.4 13.2 3.3": ["rapture"], "-0.1 2.1 5.9": ["councilmembers"], "2.8 22.1 0.7": ["apologist"], "14.6 19.4 9.3": ["tremble"], "1.1 11.4 10.4": ["waffling"], "-4.7 1.8 6.2": ["payors"], "5.1 1.8 0.9": ["dosed"], "2.8 5.2 9.1": ["megahertz"], "5.1 10.5 8.1": ["anoint"], "20.5 7.3 22.1": ["poo"], "3.7 11.9 9.9": ["regimented"], "5.9 6.3 -1.0": ["breezing"], "2.6 13.3 4.0": ["buts"], "14.0 11.2 13.0": ["winking"], "4.1 6.0 -3.7": ["retracing"], "-7.7 6.4 -0.8": ["detracts"], "-4.2 10.9 -5.2": ["eulogized"], "-0.1 7.4 3.5": ["particulates"], "4.5 7.2 3.9": ["bracketed"], "-4.2 9.5 9.3": ["annexations"], "3.9 12.8 6.4": ["predisposition"], "9.2 5.0 5.0": ["frowns"], "12.5 -7.4 1.5": ["nasdaq"], "0.6 11.7 9.5": ["scopes"], "2.9 2.4 6.7": ["guidebooks"], "-5.2 10.0 11.5": ["interferon"], "1.6 8.6 7.4": ["uncommonly"], "11.9 10.8 -1.3": ["amplifying"], "9.0 2.6 24.4": ["gastronomic"], "8.1 16.4 11.7": ["uncoordinated"], "6.7 6.9 7.8": ["thumbnails"], "6.4 19.2 13.6": ["sacrificial"], "7.1 13.0 7.4": ["blooper"], "7.2 6.3 12.2": ["prelates"], "13.2 7.3 -5.1": ["strenuously"], "10.5 1.2 19.3": ["velvety"], "4.5 8.3 10.1": ["anal"], "10.8 -3.8 0.9": ["scamming"], "5.3 19.5 -2.6": ["messianic"], "-0.3 2.3 7.9": ["procurements"], "2.3 6.2 10.3": ["chateau"], "6.5 15.2 31.2": ["schooner"], "23.6 13.9 7.6": ["pranksters"], "6.5 1.6 -0.0": ["newsmagazine"], "13.5 9.9 19.3": ["horseshoes"], "16.1 21.3 17.6": ["wimpy"], "6.8 17.1 2.0": ["magnanimous"], "6.9 10.1 8.6": ["uncounted"], "-2.9 19.3 0.4": ["refueled"], "7.1 -0.4 11.4": ["llamas"], "-1.2 7.8 1.9": ["typecast"], "-0.4 -0.8 0.4": ["repayable"], "10.8 8.1 8.3": ["netizens"], "7.3 7.5 3.1": ["honk"], "10.3 16.1 15.3": ["nothin"], "-2.1 6.9 7.7": ["deportees"], "-2.0 13.0 18.8": ["woody"], "2.6 14.2 -1.1": ["redemptive"], "4.1 12.0 3.5": ["amplifies"], "5.7 17.9 7.4": ["shamefully"], "8.5 20.2 10.5": ["fanboy"], "2.6 15.7 6.6": ["fearlessness"], "21.0 24.4 7.1": ["encircle"], "4.6 2.3 -3.0": ["alongwith"], "-0.3 14.8 8.6": ["rebelling"], "3.4 -0.7 7.0": ["augurs"], "15.0 7.5 7.7": ["cathedrals"], "4.3 13.2 10.8": ["bartering"], "7.9 3.0 5.7": ["spearheads"], "-4.0 33.6 4.4": ["demoralize"], "-1.1 35.0 5.5": ["infantryman"], "-0.8 3.4 10.7": ["muffed"], "5.7 8.0 8.4": ["banger"], "21.9 19.0 2.2": ["saviors"], "3.5 5.5 5.9": ["provisioned"], "-7.9 14.7 -0.4": ["victimize"], "6.0 1.3 -1.9": ["stereos"], "3.9 11.1 7.6": ["outrebounding"], "-2.0 7.6 3.4": ["swinger"], "7.2 15.7 5.9": ["ostensible"], "14.8 11.9 23.0": ["groundhog"], "17.3 8.8 3.3": ["imbedded"], "9.7 3.4 23.2": ["drizzled"], "-3.6 7.3 2.1": ["germane"], "7.8 10.7 13.5": ["miniatures"], "1.1 4.4 0.7": ["sensitized"], "5.3 -3.2 -0.4": ["peppy"], "0.7 -6.3 -0.5": ["resubmitted"], "1.7 -6.8 3.4": ["scrapbooks"], "8.8 13.3 5.9": ["glared"], "-1.7 7.6 12.9": ["thespian"], "5.4 4.0 0.8": ["untroubled"], "2.7 13.9 1.1": ["voiceless"], "11.3 1.9 -2.0": ["sauntered"], "11.8 -2.1 8.6": ["polycarbonate"], "0.4 6.6 10.2": ["ly"], "12.1 12.2 8.2": ["omens"], "4.2 9.8 1.0": ["untidy"], "7.8 8.7 26.7": ["clover"], "9.0 7.9 8.3": ["weirder"], "13.1 34.3 1.3": ["conquerors"], "8.1 3.1 19.7": ["sapphire"], "10.8 2.2 8.1": ["rancorous"], "23.8 5.0 2.7": ["guzzling"], "11.2 10.7 11.9": ["lusty"], "-0.0 4.4 3.3": ["absconded"], "11.9 5.6 7.7": ["gumption"], "-0.9 -1.2 -0.1": ["probity"], "-4.7 18.5 7.5": ["distrustful"], "10.1 6.1 11.7": ["stair"], "3.3 3.7 5.3": ["nos"], "5.9 4.9 20.0": ["reed"], "-7.5 9.4 9.7": ["truant"], "-0.9 11.3 10.1": ["grapplers"], "18.2 7.8 7.7": ["acquisitive"], "3.5 12.7 6.5": ["stepbrother"], "-10.2 25.6 7.3": ["disobey"], "-2.9 5.2 2.4": ["libretto"], "8.5 13.1 6.2": ["temerity"], "14.3 15.7 17.4": ["chums"], "7.7 6.1 4.9": ["spoofed"], "18.5 14.1 11.0": ["primordial"], "-1.4 12.3 25.6": ["cloves"], "-0.5 6.3 -0.1": ["personifies"], "6.7 1.7 7.5": ["budged"], "9.6 -1.0 5.9": ["dibs"], "12.0 1.6 3.8": ["bender"], "-2.4 6.7 0.5": ["achiever"], "-3.5 15.5 9.4": ["neutrals"], "-1.4 0.2 7.6": ["lumens"], "1.6 14.3 9.8": ["misfire"], "5.1 11.9 10.0": ["realtime"], "1.0 8.4 3.5": ["manholes"], "8.5 3.3 -4.1": ["expropriated"], "8.7 13.7 11.6": ["pastimes"], "2.0 18.1 22.9": ["predation"], "4.0 4.8 6.3": ["sexed"], "5.6 29.6 8.1": ["warplane"], "-1.8 3.0 7.4": ["multicore"], "-5.8 3.1 10.0": ["resales"], "9.7 4.6 14.7": ["zing"], "6.0 1.4 8.5": ["parentage"], "-0.5 12.6 6.8": ["gentlemanly"], "5.3 10.6 13.5": ["fluorescence"], "5.1 9.0 9.7": ["edicts"], "-6.8 7.9 15.3": ["sommelier"], "11.8 -2.7 -0.3": ["trialling"], "-6.0 4.6 8.5": ["heartstrings"], "-8.3 0.4 10.0": ["townhome"], "9.0 25.8 21.4": ["aphids"], "7.8 14.5 -0.4": ["preemption"], "-0.4 -0.4 -2.1": ["refiled"], "6.8 3.0 3.9": ["broadsheet"], "3.9 12.2 6.9": ["constricted"], "7.5 16.9 9.7": ["superbug"], "2.6 13.6 11.8": ["multiplication"], "-6.5 8.6 12.1": ["deacons"], "3.9 14.0 5.4": ["succumbs"], "5.7 4.5 10.2": ["brining"], "10.9 14.6 1.8": ["acquirers"], "11.8 2.4 28.8": ["capers"], "6.8 12.5 8.0": ["backpedaling"], "-0.4 12.6 15.9": ["latitudes"], "4.6 15.2 0.8": ["nameplates"], "18.5 14.0 5.8": ["ceaseless"], "16.9 -0.0 9.3": ["concessionaire"], "-0.5 7.6 14.4": ["beltway"], "1.2 20.8 4.0": ["counterterror"], "15.8 23.2 17.5": ["spammer"], "14.9 17.8 11.9": ["raindrops"], "-1.6 10.7 3.2": ["straighter"], "-6.3 4.4 5.8": ["interventional"], "12.7 5.3 3.0": ["ranted"], "-0.1 11.8 8.4": ["undressed"], "6.8 -0.8 13.5": ["powwow"], "0.2 3.0 18.9": ["preppy"], "-4.0 5.9 -1.5": ["studious"], "8.4 4.8 8.0": ["borehole"], "7.0 15.4 1.3": ["crucible"], "-1.5 13.7 6.2": ["diffused"], "-1.2 23.2 8.3": ["utterance"], "7.3 7.4 10.0": ["comforter"], "-3.3 3.5 5.7": ["pled"], "6.2 -12.4 4.0": ["wrangled"], "4.9 -2.4 11.8": ["poly"], "2.1 2.9 17.1": ["ruffles"], "-8.4 7.4 20.9": ["merlot"], "-4.3 32.9 -1.9": ["frontlines"], "15.2 15.5 5.0": ["aimlessly"], "-1.3 5.1 20.0": ["tux"], "0.3 16.4 -1.7": ["antithetical"], "5.3 6.3 29.1": ["apricot"], "-3.4 2.6 10.4": ["arias"], "6.6 3.6 7.2": ["haggard"], "5.6 1.1 4.7": ["gastric"], "-2.5 9.2 3.5": ["revelatory"], "5.0 6.9 7.7": ["int"], "1.4 0.7 5.3": ["illustrators"], "27.5 -0.1 13.1": ["emporium"], "-9.2 6.4 6.2": ["diction"], "5.8 13.2 1.3": ["uncool", "obfuscatory"], "-0.1 6.3 4.8": ["atonement"], "19.5 11.4 13.0": ["pockmarked"], "12.6 21.8 8.3": ["crazies"], "12.7 12.2 53.9": ["crayfish"], "0.1 -3.1 7.8": ["knits"], "5.0 2.9 12.0": ["railcar"], "1.5 12.9 6.5": ["manifestly"], "6.0 5.8 2.3": ["traverses"], "3.5 9.0 9.0": ["toed"], "6.8 20.0 3.8": ["parachuting"], "9.0 23.8 2.5": ["unshakable"], "-3.6 2.3 27.0": ["sherry"], "4.2 4.4 3.9": ["clubhouses"], "17.1 8.9 11.2": ["knockoff"], "5.9 16.3 5.4": ["viewfinder"], "-1.8 5.9 22.2": ["menthol"], "8.3 4.1 5.1": ["mismanaging"], "4.0 12.4 1.3": ["sanitizing"], "11.3 7.9 10.0": ["buzzwords"], "-3.0 4.4 5.3": ["incinerators"], "0.6 7.9 22.6": ["artisanal"], "11.5 -2.4 8.7": ["rosier"], "4.2 13.2 14.6": ["embellish"], "18.0 32.8 7.5": ["barbarians"], "-0.6 14.9 5.1": ["autofocus"], "-6.0 6.3 6.8": ["reallocated"], "6.9 5.0 10.0": ["crisper"], "0.5 5.3 2.7": ["coalesced"], "1.4 12.4 3.9": ["aforesaid"], "-1.7 14.5 2.1": ["operable"], "9.7 6.0 12.5": ["decayed"], "15.3 -2.0 2.1": ["quadrupling"], "-4.6 1.6 7.5": ["grantees"], "0.8 -0.3 12.8": ["concentrator"], "2.5 5.2 16.7": ["chiffon"], "4.7 8.9 -4.0": ["chastising"], "-0.6 13.6 7.1": ["feigned"], "21.5 8.8 10.1": ["twinkling"], "2.7 1.4 9.4": ["childhoods"], "-4.1 7.0 9.4": ["vagueness"], "7.3 8.4 18.8": ["spatula"], "12.7 6.2 1.2": ["windowless"], "7.8 18.1 18.7": ["bitches"], "5.3 1.5 4.1": ["sac"], "3.1 -0.3 3.7": ["paralleled"], "7.9 1.5 5.2": ["unpacked"], "6.1 22.9 23.7": ["ledges"], "2.9 7.9 15.1": ["toenails"], "0.7 -4.9 9.7": ["clenbuterol"], "1.0 5.7 4.9": ["ramble"], "-1.7 23.2 10.4": ["idealist"], "5.7 12.3 8.2": ["meaner"], "0.0 10.1 12.7": ["emigrants"], "7.2 4.9 8.8": ["bottomline"], "13.0 14.3 17.2": ["berms"], "3.1 11.1 10.0": ["northerly"], "19.3 10.2 15.1": ["snowmen"], "7.2 -1.8 8.4": ["enlivened"], "0.2 22.7 0.6": ["persecute"], "7.4 0.2 14.1": ["doggy"], "2.8 10.5 8.6": ["fistfight"], "5.9 15.8 8.7": ["tedium"], "6.6 -2.6 5.0": ["debutante"], "11.5 19.1 10.0": ["pillage"], "4.9 15.8 6.0": ["usurping"], "13.1 18.1 26.6": ["rattlesnake"], "8.1 -3.0 11.1": ["climaxed"], "-1.7 4.6 10.3": ["apportioned"], "8.0 2.0 37.5": ["ravioli"], "-7.5 -2.6 6.9": ["obstetricians"], "9.6 5.1 16.4": ["quarrying"], "7.4 3.4 13.3": ["cesium"], "-0.6 1.1 11.2": ["ballets"], "-0.2 10.8 2.3": ["pursing"], "8.8 8.5 12.1": ["blueliner"], "-5.2 3.8 11.4": ["discoloration"], "2.5 2.0 4.4": ["ment"], "21.4 1.5 0.7": ["miniaturized"], "12.7 4.6 12.5": ["ponderous"], "10.1 11.7 10.4": ["disastrously"], "0.8 21.5 12.6": ["disagreeable"], "15.8 4.2 12.1": ["sturdier"], "4.0 8.5 3.4": ["disconnecting"], "0.4 6.0 2.9": ["arousal"], "5.2 7.6 6.2": ["mended"], "10.0 7.5 11.5": ["graveyards"], "19.3 9.2 16.2": ["jousting"], "6.4 16.2 10.2": ["haughty"], "-9.2 1.9 2.9": ["hairstylist"], "0.5 10.0 3.9": ["agitations"], "-3.3 7.9 12.4": ["sulphide"], "-1.3 21.5 2.3": ["rhetorically"], "0.9 22.1 3.4": ["duality"], "0.7 9.0 4.6": ["computations"], "10.5 -1.1 2.6": ["subcontracted"], "9.3 13.5 22.2": ["icebreaker"], "4.1 5.9 2.4": ["scribbling"], "1.9 6.7 35.1": ["bream"], "-0.7 12.3 0.1": ["ypg"], "13.2 15.5 10.3": ["amorous"], "11.0 14.8 8.3": ["synonym"], "-1.9 5.0 1.2": ["acclimate"], "1.4 -3.3 -5.3": ["memorandums"], "5.7 8.5 31.0": ["salami"], "13.5 9.3 9.4": ["haha"], "8.4 13.2 15.2": ["fungal"], "3.1 2.6 6.8": ["troupes"], "2.4 19.0 0.8": ["upgradeable"], "26.0 -0.2 3.6": ["spiffy"], "8.1 3.5 1.8": ["imaged", "innovatively"], "4.6 6.2 10.2": ["hangouts", "eep"], "7.6 4.7 3.4": ["compressing"], "-0.6 12.6 7.1": ["porphyry", "nonanswers"], "2.4 2.5 5.2": ["diverged"], "0.8 9.3 6.7": ["unsatisfying"], "8.6 10.1 -3.3": ["relativity"], "5.3 4.1 4.7": ["watermark"], "3.3 -7.8 14.0": ["facials"], "5.9 9.2 9.3": ["thicken"], "6.8 18.5 23.0": ["poacher"], "10.1 -2.4 3.0": ["wowing"], "7.4 8.1 12.5": ["surmount"], "1.1 10.3 3.6": ["inundation"], "-9.8 4.4 8.4": ["relapses"], "4.9 18.7 -0.3": ["persecuting"], "-5.2 11.6 4.0": ["overburden"], "6.1 -7.2 4.9": ["dovetail"], "1.5 7.5 3.8": ["bushland"], "1.8 -8.0 6.5": ["bursary"], "-1.8 10.9 6.1": ["reconstitute"], "11.2 3.2 10.5": ["dat"], "-1.0 5.4 2.3": ["cortisol"], "5.4 7.8 3.7": ["barometers"], "11.0 14.8 9.6": ["scofflaws"], "19.3 7.7 6.0": ["verdant"], "16.3 6.4 0.3": ["prez"], "2.0 15.3 14.9": ["scalping"], "11.6 9.2 5.8": ["snorting"], "4.5 14.0 3.9": ["nationhood"], "2.2 14.5 -0.5": ["legitimizing"], "7.0 8.3 16.8": ["merriment"], "3.8 10.8 19.8": ["beekeeper"], "-1.9 7.9 4.5": ["hitchhiking"], "2.7 2.4 30.9": ["braised"], "2.1 13.5 1.3": ["naivety"], "14.8 5.2 5.1": ["playroom"], "6.7 7.6 25.8": ["mayo"], "-5.8 17.1 0.9": ["internalized"], "4.5 1.8 11.6": ["panhandle"], "22.5 -2.5 18.5": ["shaggy"], "10.4 12.4 6.9": ["splintering"], "-0.5 0.4 6.7": ["mailbag"], "0.6 5.7 3.4": ["gastroenteritis"], "6.1 7.4 3.4": ["denouement"], "5.1 3.3 9.0": ["segue"], "13.6 5.8 7.9": ["gored"], "8.8 12.3 4.2": ["vacuums"], "12.0 1.7 2.7": ["predate"], "5.0 4.6 2.7": ["compensations", "mp"], "9.6 0.5 2.3": ["outshone"], "3.3 -0.0 17.9": ["necropsy"], "2.6 15.5 3.7": ["selectable"], "7.7 9.9 5.1": ["gashed"], "3.0 19.2 10.3": ["acquiesce"], "14.0 2.1 11.1": ["corrugated"], "9.5 7.2 16.2": ["capes"], "-11.7 -3.4 1.4": ["midwifery"], "1.2 3.4 18.9": ["ska"], "10.4 -0.1 2.4": ["birthed"], "-8.0 9.9 2.3": ["countback"], "5.1 2.8 3.1": ["fieldhouse"], "1.8 13.1 9.0": ["rigidly"], "7.1 5.0 23.1": ["mink"], "5.3 2.7 9.6": ["barristers"], "6.9 6.9 17.0": ["fir"], "0.9 2.7 33.8": ["pecan"], "7.5 3.1 7.2": ["hardscrabble"], "8.1 19.6 4.1": ["capitulate"], "24.2 3.9 11.9": ["confectionary"], "3.2 -5.2 -6.4": ["arrangers"], "2.5 12.2 3.7": ["subverted"], "8.0 8.9 -1.8": ["localize"], "1.3 5.3 3.9": ["sunscreens"], "43.9 17.9 8.5": ["monolith"], "-0.5 16.2 1.4": ["deactivate"], "12.4 5.9 8.5": ["porno"], "1.5 7.3 7.0": ["dinar"], "2.3 8.8 -1.1": ["pinpoints"], "8.2 9.7 11.1": ["bookcase"], "6.6 14.5 4.8": ["deliverance"], "7.5 14.6 11.4": ["feckless"], "4.2 20.1 6.4": ["underestimates"], "0.4 14.2 12.4": ["snowplows"], "14.5 11.5 10.1": ["lynchpin"], "14.4 0.5 6.7": ["fairground"], "-3.4 3.2 15.8": ["embellishment"], "17.9 8.7 14.2": ["figurine"], "0.9 9.2 0.8": ["insinuating"], "-0.5 0.2 8.8": ["undernourished"], "8.9 13.2 13.1": ["wreaked"], "-2.2 13.9 15.8": ["resentments"], "1.9 11.2 11.4": ["exclamation"], "-6.1 11.0 13.4": ["sacraments"], "9.3 2.7 6.7": ["windup"], "-7.5 5.5 13.8": ["replanted"], "-6.3 9.7 2.9": ["frankness"], "-3.5 9.2 3.6": ["unconstitutionally"], "0.6 8.9 10.3": ["faves"], "2.9 0.4 11.1": ["guardrails"], "10.5 3.7 3.2": ["metallurgy"], "5.4 3.1 3.6": ["stanch"], "-6.0 11.7 -0.1": ["inquests"], "0.3 11.3 7.1": ["verbiage"], "11.8 9.0 6.7": ["blips"], "2.4 14.6 26.5": ["inlets"], "-1.6 15.7 10.5": ["confides"], "0.3 11.2 9.5": ["bemoans"], "2.6 6.2 4.3": ["dissipates"], "-6.1 7.7 1.2": ["reassign"], "10.0 15.3 19.1": ["knuckleball"], "13.0 6.3 5.2": ["hots"], "13.6 18.5 10.4": ["scoot"], "-0.5 6.5 5.8": ["melatonin"], "17.5 11.7 21.1": ["hippo"], "9.8 9.9 5.1": ["cajole"], "-1.9 0.8 7.9": ["decriminalization"], "4.1 5.3 5.9": ["leftfield"], "17.6 18.4 8.4": ["fart"], "0.5 6.5 7.9": ["persuades"], "12.8 -0.4 10.5": ["sequined"], "-5.8 11.1 20.1": ["legumes"], "7.2 16.0 26.4": ["carnivores"], "12.3 15.4 15.0": ["ornery"], "20.9 -1.0 4.4": ["luminary"], "7.8 2.5 14.7": ["confections"], "4.7 4.3 0.6": ["cashback"], "7.1 7.4 0.4": ["outdid"], "3.6 8.5 9.7": ["histrionics"], "11.0 0.1 -1.8": ["epitomize"], "0.6 4.6 2.8": ["supersedes"], "12.4 7.8 23.2": ["buffets"], "-8.9 8.8 9.8": ["regretful"], "18.0 21.1 12.2": ["gladiators"], "7.3 8.5 0.9": ["partitioned"], "4.7 1.8 0.1": ["flaunted"], "-0.3 1.6 10.2": ["travelogue"], "11.7 7.7 7.2": ["serendipity"], "-8.4 7.3 -0.2": ["preachy"], "3.7 6.1 4.6": ["turbans"], "4.6 11.5 9.3": ["panics"], "-2.4 14.7 5.8": ["sugarcoat"], "8.9 6.1 9.9": ["piper"], "19.6 6.1 6.1": ["bedecked"], "7.5 9.7 1.2": ["triumphing"], "13.1 11.7 15.3": ["thickest"], "5.9 13.1 -1.0": ["switchboard"], "0.3 3.7 8.7": ["expressways"], "10.1 6.1 7.7": ["welter"], "5.8 1.1 -0.3": ["unpacking"], "1.5 16.5 4.6": ["rote"], "-6.0 5.6 5.9": ["underachieved"], "-2.9 5.6 -0.4": ["deplores"], "4.9 9.8 1.5": ["coercing"], "4.4 10.6 35.5": ["seashore"], "6.9 11.4 8.6": ["hustler"], "2.0 4.6 5.1": ["meanders"], "17.3 7.5 45.2": ["otter"], "11.6 7.8 19.6": ["boob"], "2.9 3.3 1.0": ["legible"], "9.2 14.4 8.4": ["paparazzo"], "15.6 21.9 9.2": ["vastness"], "2.3 3.6 2.1": ["photoshoot"], "4.2 12.0 3.0": ["berate"], "-4.9 7.9 6.4": ["starrer"], "8.3 27.4 7.3": ["bayonet"], "-7.8 3.3 4.8": ["multipoint"], "12.7 11.5 7.0": ["scammer"], "-3.4 11.8 2.7": ["subtypes"], "4.2 7.7 6.9": ["deformity"], "15.4 0.6 9.3": ["basketballs"], "23.4 6.9 11.7": ["holographic"], "-0.2 11.1 10.1": ["urbanized"], "5.9 4.7 5.7": ["redoing"], "5.1 7.0 2.9": ["womanhood"], "12.1 5.7 1.1": ["demystify"], "-1.3 16.0 8.3": ["ruts"], "20.5 11.2 12.8": ["cavern"], "3.2 8.4 8.7": ["amygdala"], "-8.1 7.5 3.5": ["elaborating"], "1.7 -1.4 -4.5": ["accomodate"], "13.9 6.2 11.7": ["profusion"], "6.9 5.4 22.8": ["oceanographer"], "0.2 7.0 7.4": ["abdication"], "4.4 1.3 5.5": ["dataset"], "10.2 18.4 10.9": ["scowl"], "-3.0 16.4 8.6": ["quitter"], "2.1 13.1 5.0": ["nosy"], "9.5 15.6 9.4": ["bosom"], "-8.6 13.7 -0.7": ["investigatory"], "-7.7 19.7 0.1": ["confidants"], "-0.3 22.7 6.5": ["dictum"], "3.0 -3.0 8.3": ["livelier"], "-3.0 10.2 8.6": ["profanities"], "-1.0 -6.5 -0.6": ["twinning"], "6.8 7.6 5.8": ["seismologists"], "-4.8 17.0 1.5": ["commonalities"], "12.4 12.9 -0.0": ["orient"], "-7.2 3.1 9.0": ["placer"], "-2.2 0.4 6.8": ["ephedrine"], "13.8 6.1 9.2": ["coasters"], "12.2 6.6 4.4": ["chutes"], "4.7 4.1 13.2": ["synths"], "8.7 3.0 5.1": ["spry"], "2.3 17.0 10.0": ["passivity"], "-6.2 0.0 0.8": ["deputize"], "22.1 4.8 23.5": ["speckled"], "8.5 6.8 32.3": ["breakwater"], "8.9 1.2 -0.2": ["laureates"], "7.4 24.1 13.2": ["epithet"], "-1.5 6.9 0.3": ["modulate"], "4.8 6.9 4.9": ["exhausts"], "5.8 7.1 -0.3": ["contravening"], "1.2 12.0 -4.7": ["centrality"], "14.7 8.2 6.4": ["litigious"], "4.2 -3.7 2.7": ["attesting"], "-1.0 4.2 15.1": ["printmaking"], "15.5 17.3 5.0": ["hiss"], "2.9 18.0 6.3": ["misreading"], "1.5 7.8 12.2": ["unspoiled"], "-8.0 3.2 12.5": ["deduplication"], "7.7 11.2 4.2": ["schoolmate"], "2.6 4.6 8.3": ["spiel"], "3.2 10.1 5.8": ["demography"], "8.9 20.1 6.3": ["outsmart"], "6.8 -0.4 5.9": ["pimping"], "-6.2 4.1 6.7": ["stickler"], "0.7 16.0 -2.9": ["outrages"], "2.5 19.3 11.8": ["belligerence"], "6.5 13.7 8.9": ["unimaginative"], "8.3 7.1 7.4": ["mountaineer"], "4.4 19.1 3.7": ["frightens"], "11.4 17.3 2.9": ["goalpost"], "-1.9 14.4 4.1": ["respiration"], "4.4 12.0 16.4": ["eaves"], "14.2 -1.9 9.2": ["confab"], "-0.6 11.9 10.2": ["biracial"], "4.3 12.3 4.0": ["arcing"], "-2.1 11.3 7.9": ["naivete"], "6.3 5.9 -0.5": ["targetting"], "8.9 12.5 -1.5": ["embodying"], "11.7 3.3 8.1": ["trackside"], "6.1 15.7 10.5": ["outcasts"], "8.5 2.3 11.1": ["aromatherapy"], "10.5 15.0 17.5": ["dodgeball"], "18.9 14.6 16.5": ["quicksand"], "-1.4 12.4 5.1": ["coincident"], "0.1 5.7 5.5": ["premierships"], "-5.7 -0.9 2.5": ["chairpersons"], "-5.9 17.4 -2.7": ["disavow"], "4.3 4.1 3.2": ["teleconferencing"], "12.8 29.4 7.8": ["despot"], "1.7 16.1 12.7": ["fortification"], "8.9 -3.6 -0.7": ["yearold"], "-2.7 11.1 6.0": ["centerline"], "11.4 7.8 4.4": ["decimal"], "9.8 -2.8 2.2": ["zlotys"], "16.7 4.7 7.6": ["bulking"], "5.9 3.3 7.6": ["flowery"], "-4.0 4.7 0.2": ["measurably"], "0.3 17.4 5.9": ["volleying"], "18.3 25.3 11.9": ["raider"], "6.2 8.8 11.9": ["veranda"], "13.6 21.7 17.6": ["decimating"], "-1.5 23.0 10.1": ["godly"], "0.4 15.8 6.4": ["refrains"], "8.1 12.1 7.6": ["dragnet"], "2.0 5.4 1.7": ["legalities"], "-4.6 -0.6 6.2": ["frequents"], "28.7 2.9 6.1": ["dwarfing"], "-1.0 -3.2 6.2": ["overviews"], "11.1 11.1 10.2": ["luckless"], "6.2 10.5 8.4": ["bashful"], "4.7 10.5 2.2": ["antiseptic"], "6.2 7.3 7.6": ["flubbed"], "3.8 8.7 2.9": ["stifles"], "-5.6 13.0 7.4": ["quarreling"], "9.1 2.2 4.7": ["twinge"], "-7.1 11.2 -3.2": ["scriptwriter"], "21.6 -3.3 -0.8": ["revamps"], "2.8 -0.1 -2.4": ["manifestos"], "-6.4 11.3 7.0": ["generalizations"], "23.1 3.9 1.0": ["honcho"], "8.2 7.5 15.6": ["aristocrats"], "-10.3 -2.7 1.8": ["baccalaureate"], "-0.6 1.7 9.4": ["html"], "11.7 4.5 7.4": ["anorexic"], "1.1 8.1 1.8": ["infirmary"], "12.1 19.5 5.5": ["personification"], "6.0 16.9 10.3": ["asinine"], "-7.8 9.8 -0.3": ["normative"], "-3.6 11.2 5.6": ["twinbill"], "3.9 -1.2 0.8": ["concessionary"], "-7.9 0.1 2.5": ["prepayments"], "7.7 6.7 40.0": ["harvesters"], "16.6 10.4 10.6": ["doozy"], "-7.1 10.3 8.4": ["remarry"], "14.5 16.5 8.6": ["expanses"], "3.2 8.6 1.0": ["umbrage"], "9.1 8.2 7.6": ["canter"], "-5.6 4.4 6.0": ["nonpublic"], "6.5 6.0 -0.9": ["disquieting"], "-3.8 2.3 5.2": ["soph"], "-4.6 7.8 1.7": ["phrased"], "15.2 4.6 14.6": ["tits"], "8.1 15.1 5.1": ["meditating"], "11.8 12.2 7.6": ["missus"], "12.4 17.6 20.8": ["badger"], "0.0 8.3 9.3": ["fisticuffs"], "-7.7 3.9 2.3": ["recusal"], "-13.6 4.0 2.0": ["hematology"], "-0.5 7.7 4.1": ["bestowing"], "1.4 8.7 11.3": ["cheekbone"], "2.3 13.9 -2.0": ["retaken"], "2.5 3.2 5.5": ["untainted", "waterparks"], "7.4 0.6 12.6": ["diffuser"], "-1.0 10.7 9.8": ["stayer"], "19.3 11.7 26.6": ["rubbery"], "11.7 23.6 10.3": ["cyberattacks"], "9.1 4.2 13.4": ["chiller"], "12.4 3.9 5.2": ["humdrum"], "-6.7 6.0 19.3": ["riparian"], "2.6 9.7 14.7": ["dreads"], "-1.3 8.1 13.8": ["depositor"], "8.3 4.1 16.5": ["quadrennial"], "11.8 0.8 17.7": ["wavy"], "10.4 16.0 5.1": ["whoop"], "2.3 9.9 20.7": ["windsurfing"], "1.9 2.4 12.0": ["microarray"], "12.7 8.6 7.1": ["chews"], "7.3 -1.5 3.8": ["junked"], "22.6 0.0 2.8": ["clanged"], "2.7 4.0 13.8": ["subsidence"], "10.9 10.7 1.1": ["hoaxes"], "2.0 12.3 7.0": ["misrule"], "-3.9 12.7 5.7": ["prearranged"], "2.6 13.2 1.7": ["dwells"], "0.2 -1.6 14.2": ["minted"], "3.0 2.9 30.9": ["chile"], "3.6 11.7 11.4": ["inoculation"], "-1.4 9.0 11.6": ["sleeveless"], "12.9 16.0 15.3": ["gale"], "-0.0 7.9 7.4": ["superficially"], "9.2 26.0 7.7": ["outwit"], "21.3 7.4 -0.7": ["debacles"], "8.0 6.9 8.1": ["psych"], "5.8 10.4 12.3": ["shoplifters"], "11.5 9.2 5.9": ["likenesses"], "-14.7 2.4 7.4": ["opioids"], "-6.2 11.9 1.2": ["misspoke"], "17.4 12.1 8.7": ["smokestacks"], "5.2 11.8 9.5": ["tipsters"], "-1.1 11.4 7.6": ["freekick"], "9.1 -0.8 12.1": ["ebay"], "-11.4 -0.8 4.3": ["hemodialysis"], "-0.7 15.9 4.2": ["postseasons"], "1.7 11.7 8.9": ["handcuffing"], "4.1 -7.2 -4.5": ["directorship"], "4.6 14.1 4.7": ["accelerant"], "3.3 11.9 36.6": ["jetties"], "4.4 14.9 11.3": ["navel"], "12.1 1.6 0.6": ["sops"], "6.7 0.8 9.7": ["cred"], "-5.6 4.7 0.9": ["deputized"], "-2.1 -2.4 3.2": ["canonization"], "20.1 8.9 18.5": ["hunks"], "6.9 6.8 4.7": ["astrophysics"], "15.0 -0.5 12.2": ["plunk"], "7.7 7.7 13.2": ["charmingly"], "7.3 11.6 5.5": ["wincing"], "6.4 2.5 3.3": ["parastatals"], "-0.1 11.5 12.4": ["airball"], "3.4 14.8 13.7": ["subtraction"], "-3.2 11.4 5.8": ["regress"], "4.4 1.2 36.3": ["artichokes"], "-5.3 21.2 3.0": ["banditry"], "8.0 16.0 2.6": ["stopwatch"], "7.5 8.9 9.6": ["befallen", "fargo"], "1.4 12.2 15.2": ["scab"], "2.0 -3.3 1.6": ["weeklies"], "3.2 6.7 9.2": ["vignette"], "-6.1 -0.2 4.4": ["rehabbed"], "-2.0 5.8 9.5": ["portraiture"], "0.6 14.0 12.7": ["cussing"], "-0.8 5.2 4.9": ["fructose"], "-0.2 11.5 -1.0": ["functionary"], "9.5 0.4 3.9": ["ba"], "2.2 11.6 11.6": ["repaint"], "-0.2 -7.6 4.9": ["yearbooks"], "15.1 12.8 1.7": ["whizzed"], "19.2 6.6 13.0": ["serpentine"], "-0.4 2.3 -1.3": ["quizzing"], "8.9 17.8 6.1": ["underdevelopment"], "8.3 6.2 4.5": ["trod"], "7.0 8.0 9.5": ["imitations"], "-12.9 18.8 6.3": ["electable"], "4.6 3.5 11.9": ["puja"], "8.5 4.3 36.0": ["coleslaw"], "4.8 9.2 10.3": ["joe"], "-6.4 16.1 0.1": ["repeater"], "2.7 1.6 11.4": ["impressionist"], "-14.8 1.6 -0.6": ["reappoint"], "17.5 10.1 17.5": ["koala"], "5.6 2.8 10.7": ["tartan"], "-4.5 1.4 4.1": ["employability"], "1.8 4.5 -5.5": ["arrhythmia"], "2.9 6.6 3.8": ["lessee"], "-1.5 6.2 -2.2": ["revalued"], "2.7 0.6 8.8": ["hedonistic"], "-4.0 2.8 13.4": ["knitwear"], "10.9 13.0 17.4": ["fuzz"], "18.3 8.6 10.0": ["hologram"], "2.4 -2.7 12.4": ["bisphenol"], "-4.3 14.9 -5.4": ["obtainable"], "9.3 3.3 3.3": ["avidly"], "-5.8 -5.4 8.4": ["surrogacy"], "4.1 6.6 13.5": ["panhandlers"], "0.3 20.8 1.5": ["grieves"], "4.1 11.5 7.3": ["unwashed"], "5.5 18.8 -2.2": ["clandestinely"], "4.3 21.2 9.8": ["daggers"], "-1.7 11.0 3.4": ["bilaterally"], "6.6 6.8 9.4": ["salve"], "5.5 10.1 10.3": ["bandanas"], "8.1 4.8 9.8": ["wo"], "18.3 6.1 5.2": ["flog"], "0.9 5.2 5.5": ["codify"], "1.3 14.1 5.7": ["sorrowful"], "0.3 6.1 6.0": ["sexiness"], "-0.5 7.6 11.3": ["jawing"], "-3.3 1.8 13.1": ["tourneys"], "1.0 7.5 0.7": ["capably"], "10.4 15.6 3.5": ["unashamedly"], "12.3 7.4 13.0": ["shimmer"], "13.3 15.3 8.2": ["berserk"], "5.7 4.6 14.4": ["balled"], "8.5 2.1 7.5": ["sheepish"], "-8.8 0.9 0.7": ["quartile"], "4.6 4.2 2.6": ["untried"], "2.6 12.4 2.4": ["madam"], "1.1 3.3 -6.2": ["vindicates"], "-2.3 33.3 2.8": ["dishonorable"], "7.4 3.0 4.5": ["outstrips", "nightshift", "overpromises"], "3.0 20.1 3.3": ["peacekeeper"], "8.4 11.8 -1.9": ["outselling"], "13.1 -6.4 -2.6": ["trailblazing"], "1.1 17.8 7.5": ["replaying"], "2.3 15.1 2.1": ["glorification"], "1.8 8.4 8.2": ["abscess"], "8.0 3.4 13.3": ["paneling"], "8.0 7.0 4.7": ["cajoling"], "1.0 6.1 10.1": ["naturalistic"], "-12.2 16.6 6.2": ["electability"], "3.9 17.0 10.2": ["randomness"], "7.9 12.1 12.8": ["meshing"], "0.9 9.7 9.7": ["shifter"], "9.1 31.3 11.2": ["fortifications"], "-1.7 15.9 3.7": ["abductees"], "4.5 -1.2 10.0": ["highbrow"], "5.9 5.7 26.4": ["overcooked"], "11.9 25.3 7.1": ["despots"], "12.5 11.7 8.8": ["blissfully"], "9.0 5.6 20.9": ["shanties"], "4.5 0.4 15.9": ["sealant"], "14.6 9.2 18.7": ["snares"], "14.5 2.6 15.0": ["waistlines"], "4.6 5.9 2.8": ["vapid"], "2.2 6.1 3.5": ["forgetful"], "5.5 12.1 8.7": ["anachronism"], "5.4 6.0 28.0": ["puree"], "3.4 14.5 2.6": ["unappreciated"], "-1.3 8.2 5.0": ["dilutes"], "-0.0 9.1 9.1": ["docetaxel"], "8.4 -0.2 14.4": ["lil"], "9.7 8.6 8.3": ["gander"], "-2.7 5.0 4.8": ["indulges"], "-8.0 1.5 -1.8": ["deeded"], "3.9 -1.5 4.6": ["alleviates"], "6.2 13.4 1.8": ["devaluing"], "7.3 4.6 5.4": ["laugher"], "4.5 12.8 8.0": ["astrologer"], "3.8 6.8 5.6": ["sendoff"], "4.5 12.6 8.1": ["roughest"], "12.9 -1.7 -1.1": ["duping"], "12.7 4.1 21.0": ["llama"], "-0.5 4.1 6.7": ["diuretic"], "20.0 7.9 4.1": ["glowed"], "-2.5 5.7 13.4": ["sartorial"], "3.5 6.0 2.4": ["gd"], "11.7 11.6 5.1": ["covets"], "-5.7 12.7 8.6": ["malignancies"], "7.7 14.2 29.9": ["holly"], "9.6 10.0 1.5": ["dozing"], "-3.7 10.9 12.0": ["procreation"], "10.0 28.0 9.9": ["wimp"], "12.5 9.5 5.5": ["cesspool"], "2.2 0.2 13.7": ["droll"], "-0.8 2.8 1.5": ["sportspersons"], "14.2 3.5 6.1": ["gawk"], "-1.2 0.3 9.2": ["leptin"], "5.6 17.3 20.0": ["crewmates"], "2.0 0.7 13.7": ["eyeliner"], "6.5 12.9 26.3": ["mite"], "8.9 9.9 3.6": ["rucksack"], "-2.9 8.0 8.8": ["handoffs"], "-1.9 1.0 5.7": ["dramatics"], "3.3 9.7 12.3": ["monotone"], "4.5 14.0 7.4": ["anyplace"], "5.0 7.7 6.5": ["repurchasing"], "-2.5 5.1 1.9": ["outdueled"], "5.8 0.8 36.2": ["pickled"], "7.8 11.1 9.1": ["hokey"], "14.1 6.5 14.8": ["fossilized"], "6.6 13.5 2.2": ["teargas"], "13.5 3.3 7.2": ["addled"], "-3.4 3.2 0.3": ["durations"], "0.0 2.3 4.3": ["freeware"], "8.5 21.7 8.3": ["flinched"], "0.6 8.4 1.4": ["swissinfo"], "17.0 3.7 17.3": ["lovin"], "3.5 2.3 13.3": ["comedienne"], "-2.3 7.1 15.1": ["horticulturist"], "5.7 5.4 8.3": ["terraced"], "8.8 17.2 12.2": ["potions"], "9.0 6.2 3.4": ["punctures"], "20.0 16.2 7.9": ["airship"], "-2.2 4.4 27.8": ["buttermilk"], "5.7 -0.5 8.7": ["booties"], "12.1 0.1 12.5": ["lube"], "-3.2 11.6 6.7": ["abrasion"], "7.6 12.5 11.2": ["staccato"], "6.1 1.7 11.9": ["byte"], "-4.6 18.0 13.8": ["triggerman"], "17.1 3.1 -1.1": ["woos"], "11.0 13.8 6.2": ["granddad"], "3.4 4.5 47.9": ["fillet"], "6.4 18.1 5.5": ["miscalculations"], "-1.7 7.1 7.6": ["tolerances"], "5.5 26.6 4.5": ["acolytes"], "16.9 21.0 6.1": ["ungodly"], "2.7 0.8 12.5": ["headbands"], "-4.4 13.3 7.4": ["demilitarization"], "-10.3 4.5 10.1": ["ribavirin"], "-2.0 11.6 11.7": ["sternum"], "9.6 2.9 13.1": ["wiggled"], "6.9 6.5 12.6": ["tipsy"], "-0.3 4.2 5.1": ["recombinant"], "3.1 12.6 4.5": ["befriending"], "-2.4 4.7 11.5": ["gratuities"], "-4.1 6.5 2.2": ["outpitched"], "3.2 11.8 1.0": ["transiting"], "6.3 3.5 24.2": ["wok"], "1.7 13.0 14.4": ["lightweights"], "15.8 6.9 19.1": ["glassy"], "12.5 19.5 -1.1": ["autonomously"], "14.3 17.9 8.0": ["fiercer"], "-6.8 9.5 3.8": ["jell"], "2.4 4.4 9.1": ["racquetball"], "3.3 19.5 4.5": ["intransigent"], "14.3 10.7 3.4": ["greeter"], "13.3 23.0 7.5": ["decapitation"], "6.9 8.9 17.1": ["humps"], "9.9 13.8 4.7": ["foretold"], "-2.1 6.5 1.8": ["emigrating"], "11.8 10.7 10.3": ["shoves"], "-5.2 9.9 16.3": ["foresters"], "-4.5 8.5 3.7": ["moreso"], "12.7 5.2 20.9": ["pagoda"], "-0.3 10.1 -0.1": ["requisition"], "11.3 3.8 23.4": ["pelt"], "10.1 4.4 6.1": ["haywire"], "-7.5 10.8 3.8": ["modality"], "4.6 3.7 2.1": ["respirators"], "15.2 11.1 23.9": ["shipbuilder"], "7.8 12.8 5.3": ["wifi"], "-1.4 -5.6 9.0": ["wk"], "9.5 7.5 0.0": ["musty"], "7.9 6.6 24.6": ["teak"], "3.8 -1.0 9.1": ["caning"], "14.0 10.8 9.9": ["hex"], "4.6 13.1 7.8": ["loony"], "9.8 5.7 2.9": ["spellbinding"], "8.8 4.1 9.0": ["shantytowns"], "2.6 4.4 6.9": ["pensive"], "7.6 8.8 6.4": ["pliable"], "-14.4 10.5 17.8": ["antivirals"], "-5.6 8.3 6.1": ["disown"], "7.8 19.5 5.8": ["archetype"], "-5.3 0.0 2.4": ["reconvenes"], "-1.5 15.4 11.1": ["dribbler", "humors"], "8.7 6.9 5.7": ["storeroom"], "-6.1 12.7 16.7": ["fungicide"], "13.9 7.0 60.6": ["crustaceans"], "-0.7 0.7 4.1": ["boepd"], "0.4 10.0 8.2": ["shekel"], "-0.8 13.7 2.1": ["conceptions"], "27.5 5.0 3.0": ["biggies"], "0.0 1.8 4.1": ["odometer"], "15.0 2.1 -2.1": ["popularizing"], "5.2 11.2 2.6": ["uncluttered"], "-3.3 5.6 17.2": ["lakeshore"], "19.2 1.1 5.9": ["squeaking"], "-7.6 3.0 8.7": ["regionalization"], "10.6 9.3 8.0": ["gents"], "-4.8 12.6 4.1": ["slighted"], "1.9 -5.3 4.7": ["padlocked"], "-0.2 0.4 5.3": ["enthuses"], "3.1 0.9 2.1": ["shampoos"], "2.6 29.8 7.8": ["marksmen"], "7.6 11.2 8.2": ["daydream"], "7.7 5.3 5.6": ["kinky"], "9.7 -2.2 7.5": ["cashes"], "4.3 5.7 4.0": ["grist"], "-5.6 30.5 0.6": ["disloyalty"], "4.7 12.1 11.7": ["depressions"], "-1.1 6.4 0.5": ["bestows"], "6.2 8.8 8.9": ["dawns"], "11.2 22.7 5.7": ["truest"], "7.9 3.2 6.2": ["cladding"], "20.7 2.2 10.7": ["gangly"], "1.9 11.1 1.0": ["tinnitus"], "6.7 4.3 1.3": ["pestered"], "-2.7 -1.6 0.7": ["notarized"], "11.0 7.8 19.7": ["crock"], "-3.9 -4.1 0.1": ["encoders"], "9.4 11.6 3.8": ["curvature"], "-2.8 9.1 8.8": ["cellars"], "14.3 13.1 5.8": ["pistons"], "3.2 -0.6 1.4": ["securitizations"], "6.5 6.3 30.2": ["oregano"], "13.2 -2.2 14.2": ["munched"], "5.7 14.4 7.0": ["cleverness", "hackdom"], "19.5 8.3 11.8": ["coiled"], "8.6 13.3 9.0": ["contorted"], "5.4 7.0 9.5": ["unshaven"], "2.9 14.5 5.9": ["happenstance"], "-3.5 4.9 12.8": ["childbearing"], "11.0 17.4 3.0": ["lunatics"], "10.7 4.3 16.5": ["lollipops"], "-6.5 -1.2 6.1": ["instrumentalists"], "6.8 4.6 3.2": ["unsanctioned"], "9.0 -2.8 19.2": ["quarts"], "-4.6 13.6 7.3": ["typhoid"], "4.4 -4.6 1.0": ["nappies"], "-4.6 9.9 -5.4": ["executors"], "0.2 1.3 11.0": ["republish"], "3.6 0.9 1.6": ["latching"], "13.8 1.8 7.5": ["transvestite"], "14.3 8.8 27.9": ["roach"], "6.8 18.2 25.4": ["sparrows"], "11.4 19.3 7.9": ["saps"], "-4.7 5.9 6.4": ["clopidogrel"], "14.6 7.2 18.1": ["mouthwatering"], "7.2 19.7 12.7": ["leaderboards"], "2.9 4.1 -1.4": ["congrats"], "-1.6 14.7 5.8": ["compulsions"], "9.8 5.7 8.1": ["straddled"], "1.8 2.3 0.4": ["recieve"], "-0.2 11.0 7.7": ["resents"], "24.3 5.4 9.7": ["plop"], "11.5 7.7 5.9": ["infantile"], "4.8 17.8 6.5": ["intoned"], "8.0 6.7 10.5": ["densely"], "12.8 9.6 11.2": ["peeps"], "9.1 6.5 8.8": ["unperturbed"], "3.8 -1.7 -2.8": ["entrusting"], "8.0 12.4 14.0": ["elixir"], "10.6 9.6 6.5": ["thrall"], "6.7 5.9 1.7": ["stylishly"], "3.2 11.2 3.4": ["plotline"], "6.8 11.4 2.6": ["goaded"], "-4.2 -1.4 14.0": ["alpacas"], "-2.5 11.3 -3.3": ["pluralistic"], "-2.5 15.3 0.7": ["statesmanship"], "-3.3 11.4 9.2": ["policymaker"], "8.2 9.4 -1.8": ["electrically"], "-1.0 -1.0 5.1": ["dharna"], "5.5 6.2 0.9": ["refines"], "10.4 5.4 6.0": ["poisonings"], "1.3 14.6 10.9": ["sledging"], "7.7 2.8 -0.0": ["dispelling"], "3.6 8.3 2.8": ["retrench"], "0.5 2.2 3.7": ["nutraceutical"], "12.7 -2.5 8.3": ["pizzazz"], "3.0 11.5 1.3": ["theorist"], "28.5 10.0 25.5": ["whopper"], "7.8 1.6 29.2": ["pistachio"], "-4.2 2.5 6.6": ["employable"], "5.6 8.1 0.7": ["embarrassments"], "2.5 13.8 23.8": ["hummingbirds"], "5.3 10.7 -3.1": ["comprehensible"], "1.2 -1.2 14.7": ["frocks"], "11.7 11.4 0.9": ["hyperbolic"], "6.2 13.0 1.2": ["goosebumps"], "2.3 17.4 8.9": ["deterrents"], "1.4 7.8 12.4": ["gravestone"], "4.0 -8.2 -1.4": ["roadshows"], "4.6 2.3 4.7": ["grafted"], "5.5 15.5 4.3": ["relearn"], "0.9 13.7 18.9": ["spinnaker"], "1.7 4.5 11.8": ["dioxins"], "5.7 11.3 7.4": ["trajectories"], "16.6 4.5 5.0": ["cavorting"], "-2.2 6.7 2.5": ["encumbered"], "3.5 25.0 1.2": ["dehumanizing"], "-6.6 10.8 5.6": ["flippant"], "6.4 9.4 17.8": ["bogs"], "12.1 -3.0 1.7": ["repurposed"], "1.8 4.8 -0.6": ["helpdesk"], "10.7 12.8 9.4": ["grunting"], "17.9 45.9 9.0": ["baddies"], "5.7 2.1 -2.0": ["impersonated"], "3.4 10.4 12.7": ["lifter"], "-1.8 6.0 3.1": ["hydrologist"], "5.2 7.8 17.7": ["eggnog"], "3.2 3.8 7.6": ["plaintive"], "7.1 9.9 22.5": ["tongs"], "10.5 15.2 33.2": ["invertebrates"], "4.9 1.2 2.1": ["titillating"], "7.2 2.3 15.2": ["thongs"], "-7.9 8.7 3.6": ["catholic"], "4.3 11.0 4.3": ["purges"], "10.3 7.9 -1.4": ["concourses"], "-4.5 6.6 2.1": ["prefaced"], "1.4 13.6 -1.8": ["deflects"], "-3.7 -2.2 5.6": ["tenors"], "8.1 13.9 4.9": ["whores"], "6.2 3.7 7.8": ["clothe"], "-1.4 11.8 8.8": ["executable"], "-7.4 4.9 17.8": ["foodgrains"], "-1.9 7.9 2.0": ["homeopathy"], "1.8 -5.5 -0.5": ["cosponsored"], "4.7 6.2 -0.7": ["counteroffer"], "15.6 -1.1 4.7": ["shoebox"], "9.6 16.6 10.9": ["sneering"], "3.2 17.5 8.9": ["sulk"], "6.5 3.6 0.6": ["kobo"], "7.1 18.3 -6.2": ["chaff"], "4.7 11.2 6.5": ["saintly"], "5.9 2.5 5.7": ["squelched"], "-3.7 26.3 -0.3": ["interlocutor"], "3.7 4.3 5.7": ["milepost"], "13.6 -5.8 3.5": ["fleeced"], "14.2 8.9 5.4": ["crisscross"], "18.8 25.1 13.1": ["goblins"], "10.6 47.6 0.9": ["guerillas"], "10.1 10.2 -1.4": ["cornfields"], "-3.6 -0.4 4.6": ["presale"], "5.3 21.6 11.1": ["demagoguery"], "18.0 3.9 10.2": ["midgets"], "0.3 2.5 7.4": ["merrier"], "-7.6 9.0 7.2": ["touchback"], "4.6 17.3 9.0": ["neutrons"], "3.9 9.0 55.9": ["swordfish"], "20.5 10.2 6.7": ["phoenix"], "3.2 17.0 11.4": ["flyby"], "3.2 5.6 4.2": ["preexisting"], "0.7 -1.9 5.7": ["pharmacokinetics"], "17.7 1.5 3.0": ["blowup"], "7.2 6.3 1.3": ["spartan"], "2.3 0.6 0.8": ["concessional"], "6.1 11.1 24.1": ["steamer"], "-0.4 0.0 5.0": ["rummage"], "12.9 10.9 9.6": ["hillbilly"], "13.9 12.1 3.7": ["defacing"], "-2.0 6.8 10.9": ["frosh"], "17.9 11.3 15.7": ["glint"], "1.8 9.4 7.7": ["canvassers"], "5.1 7.1 10.8": ["chairlift"], "7.1 17.8 17.5": ["skunks"], "14.9 10.4 14.6": ["dismembering"], "-2.9 5.9 1.8": ["newsmakers"], "5.0 2.1 9.0": ["peels"], "6.3 -1.7 3.2": ["toxicologist"], "3.6 5.2 1.3": ["scribble"], "20.6 7.6 6.7": ["wobbles"], "4.5 4.8 7.7": ["hazmat"], "-5.9 4.1 1.8": ["layover"], "-6.5 4.6 -0.1": ["punctual"], "12.7 2.0 -0.4": ["noncash"], "11.0 5.5 2.3": ["vacuous"], "8.4 3.7 5.2": ["doped"], "1.7 15.7 46.2": ["tarpon"], "14.5 -0.5 3.2": ["jingles"], "1.0 -0.6 14.4": ["divvied"], "14.5 17.0 5.0": ["accidently"], "15.4 12.6 15.6": ["octagon"], "6.4 15.3 22.8": ["trapper"], "2.1 10.2 9.6": ["satirist"], "9.3 21.6 4.0": ["arrogantly"], "-2.9 2.8 4.5": ["acquittals"], "2.1 9.6 11.0": ["wikis"], "6.8 5.1 5.8": ["midwestern"], "16.1 1.0 11.4": ["gyrating"], "-9.6 4.4 13.1": ["platelet"], "10.9 10.0 -4.5": ["inbuilt"], "22.1 24.7 9.1": ["intergalactic"], "4.7 5.8 16.4": ["highland"], "-7.6 4.7 11.0": ["formulary"], "3.1 10.2 2.9": ["outplaying"], "4.1 1.9 13.0": ["skatepark"], "3.3 7.3 11.0": ["cattlemen"], "13.2 4.9 6.8": ["moneymaking"], "12.3 4.1 9.6": ["stuffs"], "2.2 -0.2 1.5": ["impinge"], "6.0 11.3 -0.2": ["snoop"], "-5.4 3.7 3.4": ["reexamine"], "-5.1 7.4 -1.4": ["fictionalized"], "10.5 12.3 2.2": ["gaseous"], "2.9 17.2 3.9": ["executioners"], "7.4 5.7 9.9": ["canteens"], "2.7 11.5 20.6": ["crankbaits"], "-1.6 1.7 8.1": ["repricing"], "15.0 8.4 8.7": ["headdress"], "6.4 7.5 0.9": ["boggles"], "16.6 12.7 17.2": ["quivering"], "-2.4 15.7 3.8": ["wetting"], "0.3 6.5 -0.8": ["ramblings"], "5.4 10.1 4.9": ["rebukes"], "8.7 9.1 16.0": ["ecologists"], "17.4 17.9 3.3": ["marketshare"], "13.7 3.1 9.8": ["hoists"], "14.0 15.8 13.6": ["hermit"], "-3.4 5.9 0.6": ["handedness"], "4.6 3.2 21.8": ["crepes"], "8.7 0.6 6.3": ["quickie"], "2.4 10.7 3.6": ["catcalls"], "9.6 10.7 10.6": ["daydreaming"], "12.7 6.6 9.2": ["gyroscope"], "-7.5 15.6 6.7": ["premeditation"], "6.9 5.3 -0.6": ["actuators"], "12.3 16.6 9.5": ["chink"], "2.8 5.7 6.2": ["crystallize"], "-4.2 6.9 4.6": ["dramatization"], "3.4 21.1 10.6": ["photon"], "2.9 10.9 18.0": ["shank"], "11.1 13.8 27.2": ["morsel"], "3.6 7.2 5.0": ["topology"], "12.3 20.2 6.2": ["gadgetry"], "-5.0 1.7 6.8": ["recertification"], "15.0 13.8 12.2": ["twirl"], "12.3 8.5 12.3": ["papa"], "5.2 19.4 0.5": ["muslims"], "6.1 12.4 21.5": ["nightcrawlers"], "12.6 3.2 13.9": ["juts"], "1.3 20.0 13.9": ["strategizing"], "13.7 9.0 21.5": ["speared"], "8.7 12.2 6.5": ["successively"], "-3.0 12.6 10.6": ["knockdowns"], "-10.1 7.8 12.8": ["intoxicants"], "3.6 13.1 5.5": ["overtaxed"], "-5.9 4.7 8.7": ["soldering"], "6.9 6.3 9.5": ["reflectors"], "-9.8 8.0 -1.3": ["reread"], "8.6 16.9 12.0": ["stinker"], "12.1 7.4 5.3": ["trounce"], "-3.7 8.0 8.0": ["femtocells"], "2.6 15.4 5.0": ["insinuation"], "0.4 20.1 3.2": ["redeploying"], "12.7 3.4 7.3": ["amok"], "-3.0 8.7 17.8": ["johns"], "-4.1 6.5 11.3": ["disenfranchisement"], "-6.0 3.0 8.7": ["instrumentals"], "9.5 8.9 8.2": ["peculiarities"], "3.8 5.0 7.4": ["toasty"], "8.7 7.7 8.8": ["baffle"], "-5.8 3.7 -4.6": ["electrolytes"], "5.7 10.7 8.9": ["bombast"], "6.1 14.0 5.4": ["schematic"], "-7.0 10.7 10.8": ["pinfall"], "2.2 18.6 7.6": ["unwisely"], "10.5 -1.0 4.6": ["spurn"], "-7.8 1.4 3.8": ["deliverability"], "10.0 16.4 7.0": ["ascendant"], "-7.6 -1.3 -1.6": ["letterwinners"], "5.8 9.9 0.3": ["snowbound"], "5.6 12.5 9.7": ["humorously"], "-2.0 12.2 8.9": ["reentry"], "29.4 -1.3 9.4": ["outsize"], "12.5 3.4 10.1": ["pulley"], "21.7 9.9 28.0": ["croc"], "5.6 3.9 14.9": ["garlands"], "8.8 12.0 3.7": ["panes"], "6.2 -0.3 8.3": ["jatropha"], "5.4 8.2 34.5": ["papaya"], "14.8 7.9 15.8": ["jaguar"], "-2.4 -6.6 -1.5": ["roundtables"], "7.4 26.3 2.6": ["stooge"], "12.8 11.6 12.4": ["glands"], "5.8 10.9 24.4": ["fruitcake"], "17.9 -1.9 0.5": ["towered"], "26.8 30.9 14.9": ["armada"], "13.8 3.4 7.2": ["squeals"], "5.1 16.5 1.6": ["magnification"], "5.5 0.9 -3.0": ["dba"], "20.5 2.2 0.8": ["catapulting"], "1.8 13.5 0.7": ["desirous"], "0.1 0.4 7.1": ["plugins", "postmark"], "15.6 11.7 2.6": ["appeased"], "-1.7 -1.5 6.2": ["dramedy"], "3.5 8.0 26.9": ["stews"], "10.1 12.5 0.4": ["interlinked"], "6.1 6.6 0.7": ["detains"], "14.4 -5.7 -6.6": ["inaugurates"], "-5.4 11.2 9.9": ["opiate"], "8.3 10.2 17.2": ["kickball"], "15.6 20.6 15.8": ["potion"], "6.6 22.7 6.2": ["trespassers"], "7.7 7.7 14.2": ["bobblehead"], "-3.7 11.3 4.5": ["hustings"], "10.9 17.9 18.0": ["yin"], "3.9 15.5 7.1": ["numerically"], "-1.7 4.5 20.1": ["snowbirds", "outfall"], "0.4 7.2 12.4": ["slacking"], "8.3 11.1 4.1": ["indignities"], "6.6 5.2 -3.9": ["adjoins"], "1.5 3.9 6.9": ["typos"], "4.5 15.3 6.4": ["insufferable"], "6.3 -5.2 4.7": ["reinstates"], "13.8 8.0 31.1": ["gourds"], "14.1 10.3 4.8": ["czars"], "3.2 17.5 -2.1": ["pitfall"], "4.9 8.0 0.3": ["allude"], "8.3 0.9 11.6": ["shoelaces"], "3.5 9.9 8.2": ["morgues"], "-2.1 11.8 6.7": ["nicks"], "10.1 4.7 16.8": ["claycourt"], "8.0 8.4 12.9": ["botanist"], "-4.2 4.5 6.3": ["overwork"], "0.6 2.9 3.7": ["holistically"], "2.2 9.6 1.1": ["creases"], "0.9 30.0 4.3": ["steadfastness"], "-2.8 12.5 1.2": ["poignantly"], "1.8 12.8 13.9": ["outlier", "umph"], "-6.8 0.9 7.3": ["rehiring"], "7.0 10.5 1.6": ["stabilizer"], "-0.7 -4.3 10.5": ["proms"], "13.1 29.6 13.4": ["captor"], "11.6 12.9 24.4": ["falcons"], "5.9 1.6 12.6": ["junkets"], "-0.1 7.1 4.8": ["retold"], "14.1 11.1 6.7": ["iconography"], "8.1 6.0 2.3": ["washrooms"], "8.9 3.0 0.3": ["pedometer"], "9.9 10.4 19.8": ["hotdogs"], "14.3 8.6 25.1": ["saucer"], "-4.5 4.8 6.8": ["vanadium"], "8.2 10.8 6.3": ["deride"], "10.2 0.6 1.2": ["decelerate"], "-8.2 11.9 1.2": ["renunciation"], "15.3 18.6 24.2": ["roaches"], "0.4 -1.7 6.5": ["prospectuses"], "9.7 19.7 8.9": ["inscrutable"], "0.8 12.7 9.0": ["amputate"], "-3.8 9.9 6.9": ["brows"], "5.0 8.4 33.9": ["coriander"], "-1.8 9.7 -0.1": ["marshalled"], "-4.3 10.8 3.4": ["misbehave"], "0.7 3.6 10.1": ["docent"], "13.8 4.2 13.6": ["monthslong"], "11.2 6.0 10.7": ["grownups"], "11.8 29.0 6.6": ["terrors"], "-2.8 10.0 0.5": ["indicting"], "-6.6 6.8 1.0": ["substantively"], "-12.7 7.5 2.4": ["teamer"], "8.2 7.0 16.3": ["overabundance"], "6.6 19.9 8.1": ["obfuscation"], "-2.6 6.7 2.7": ["imbibe"], "-2.7 -1.0 9.2": ["grafting"], "9.3 10.7 4.0": ["cringing"], "8.9 19.7 -0.0": ["fortifying"], "-0.1 20.0 4.7": ["mantras"], "-5.7 3.5 6.7": ["disbursing"], "11.9 11.7 1.6": ["shirking"], "17.1 23.0 28.9": ["grasshoppers"], "9.7 10.1 17.3": ["mammalian"], "4.4 24.6 4.6": ["duplicitous"], "6.8 16.3 7.0": ["eyesores"], "5.3 9.5 7.5": ["usernames"], "0.1 5.3 14.0": ["undertone"], "22.1 15.3 19.1": ["squishy"], "2.0 8.9 23.5": ["dinnertime"], "-3.7 1.2 12.3": ["halter"], "12.9 3.9 9.2": ["shantytown"], "16.3 11.7 11.5": ["incipient"], "-2.1 11.6 -3.0": ["figment"], "27.1 20.4 26.6": ["scorpion"], "1.2 2.8 7.0": ["whodunit"], "8.6 4.1 7.0": ["diode"], "6.2 9.9 19.9": ["subspecies"], "10.4 13.5 7.4": ["gazes"], "3.6 12.5 10.1": ["extant"], "2.5 6.7 16.7": ["braid"], "11.3 7.8 10.1": ["rangy"], "-0.5 7.9 1.3": ["disapproves"], "8.3 6.9 7.1": ["stashing"], "-1.4 4.2 0.1": ["beatified"], "12.8 9.4 10.1": ["supergroup"], "6.3 5.3 1.0": ["reinstall"], "0.4 9.3 11.3": ["navigable"], "-3.3 2.0 8.6": ["ovulation"], "-4.7 19.0 1.7": ["revisionist"], "0.2 8.8 9.1": ["collectives"], "4.1 6.7 12.0": ["paddocks"], "2.5 -3.7 3.5": ["doctorates"], "13.5 10.0 16.1": ["yer"], "12.2 19.4 4.4": ["fanboys"], "2.5 4.0 14.5": ["matted"], "0.3 19.0 -1.9": ["unvarnished"], "3.2 9.1 5.0": ["buffering"], "4.4 11.1 4.3": ["saturate"], "11.6 12.5 7.3": ["pugnacious"], "12.2 7.7 15.5": ["dyke"], "1.1 5.6 7.4": ["obligate"], "-4.0 10.7 6.0": ["uplink"], "27.4 5.1 7.4": ["newfangled"], "7.2 25.0 4.4": ["stalkers"], "-6.8 6.3 10.8": ["downlink"], "-4.0 16.1 6.1": ["constants"], "-0.7 14.7 11.6": ["persevering"], "-1.8 -1.2 2.9": ["inclusions"], "-11.9 17.7 5.7": ["confide"], "-3.3 11.7 7.6": ["pickoff"], "6.6 16.7 16.8": ["hierarchies"], "1.7 16.7 11.9": ["hesitates"], "5.1 22.5 8.9": ["realists"], "6.4 -0.1 9.4": ["luxe"], "1.4 4.9 1.9": ["telephonic"], "-11.1 20.1 8.0": ["paraphrasing"], "13.8 -3.8 10.2": ["slicked"], "-2.0 -3.5 3.9": ["panellists"], "1.2 8.7 5.6": ["didn"], "9.6 12.1 20.1": ["chisel"], "3.5 8.8 4.6": ["psychics"], "8.8 -0.3 6.3": ["laundromat"], "18.3 9.5 6.3": ["zillion"], "12.2 6.6 13.9": ["stunting"], "6.8 4.7 14.4": ["firetruck"], "-5.2 5.0 9.5": ["quilters"], "-3.3 11.3 3.5": ["understeer"], "8.4 3.8 7.0": ["manicures"], "10.4 6.5 3.5": ["intercontinental"], "9.1 -2.9 8.2": ["mars"], "11.4 0.4 25.7": ["peacocks"], "3.2 29.3 4.1": ["platoons"], "5.1 12.9 6.0": ["placeholder"], "7.9 12.1 -1.5": ["inconspicuous"], "20.6 11.9 19.3": ["gnarly"], "7.1 1.2 -0.3": ["reclassify"], "13.2 11.3 9.0": ["intricately"], "14.8 6.0 -3.6": ["paragon"], "22.2 6.0 8.0": ["lumbered"], "4.9 -8.5 0.4": ["perused"], "0.9 1.7 17.2": ["mince"], "10.0 11.5 -0.5": ["resoundingly"], "8.8 0.6 -2.0": ["unseal"], "6.6 6.7 7.2": ["zips"], "12.7 1.3 7.9": ["gangbusters"], "3.3 -3.6 12.7": ["socialites"], "15.1 15.9 34.7": ["possum"], "-3.9 -1.1 9.4": ["overspent"], "10.8 5.6 6.7": ["bares"], "18.0 4.9 12.0": ["geyser"], "-3.2 9.1 10.8": ["pant"], "3.5 6.4 1.5": ["couldnt"], "4.3 16.0 5.3": ["epitaph", "desensitise"], "6.0 12.8 12.3": ["snobbery"], "9.0 4.8 13.6": ["roofer"], "3.7 9.3 6.5": ["bitching"], "-1.9 12.6 18.6": ["craps"], "4.7 8.4 6.9": ["afterglow"], "3.2 19.2 7.2": ["exes"], "1.3 15.1 4.5": ["outplay"], "7.2 11.8 6.2": ["hotbeds"], "13.1 3.9 15.8": ["fests"], "8.4 19.1 4.8": ["phobias"], "-0.0 3.5 -4.6": ["metabolites"], "2.2 3.5 0.2": ["dyslexic"], "5.6 0.3 7.5": ["signups"], "-0.8 7.1 -6.4": ["implicates"], "0.7 8.3 5.4": ["choreograph"], "8.4 5.8 -0.5": ["inundate"], "-0.1 4.6 3.1": ["oneworld"], "15.4 22.7 17.2": ["brawler"], "-4.4 14.3 2.7": ["ascertaining"], "1.1 1.4 3.8": ["keener"], "12.1 12.6 9.5": ["chicanery"], "-5.2 -1.3 13.7": ["thimerosal"], "9.7 0.5 11.2": ["migrates"], "13.4 4.6 3.5": ["offshoots"], "5.5 -0.9 1.7": ["broadsided"], "11.2 11.1 17.3": ["puke"], "11.8 28.3 3.7": ["stooges"], "1.0 11.5 6.2": ["deduced"], "-0.6 14.1 14.4": ["demarcated"], "17.4 12.6 16.2": ["craggy"], "8.8 6.1 1.1": ["lessor"], "-1.5 3.2 8.8": ["sovereigns"], "3.4 14.6 3.3": ["idolatry"], "8.1 8.0 7.7": ["escapade"], "-4.1 16.4 4.5": ["disobeyed"], "9.2 9.7 6.2": ["hailstorm"], "1.6 11.9 7.5": ["macrophages"], "-2.1 7.4 23.6": ["carryout"], "-0.4 7.1 2.8": ["roundups"], "-0.8 6.5 9.1": ["directionless"], "2.6 4.7 9.1": ["sextet"], "10.9 10.2 1.9": ["staggeringly"], "-4.3 10.2 5.7": ["religiosity"], "6.1 3.6 15.8": ["patina"], "7.5 2.2 11.7": ["larynx"], "12.2 11.8 -0.1": ["firebombing"], "7.5 1.5 3.5": ["predominate"], "-2.7 2.1 3.0": ["curricular"], "6.7 -6.6 -1.3": ["dovetails"], "15.9 14.1 4.3": ["reincarnated"], "4.2 4.1 6.5": ["undies"], "9.8 -2.4 4.7": ["wads"], "10.1 3.3 18.6": ["albino"], "7.0 2.7 20.9": ["flax"], "-1.2 5.5 7.5": ["cultivates"], "6.6 6.2 10.3": ["dreamlike"], "0.8 9.1 11.9": ["interracial"], "3.3 5.6 8.4": ["ac"], "-7.0 4.4 -2.7": ["intercession"], "7.5 -0.7 1.7": ["capstone"], "4.9 21.6 4.9": ["disorientation"], "2.1 14.4 1.4": ["chastise"], "14.5 6.5 9.3": ["affix"], "15.7 10.4 4.1": ["dripped"], "6.3 1.9 8.7": ["stylings"], "-2.8 8.4 6.4": ["tritium"], "-1.5 -0.7 1.1": ["scheduler"], "10.3 16.0 7.8": ["dank"], "13.2 13.4 8.7": ["brainpower"], "1.8 12.6 -1.1": ["expansionary"], "8.8 9.8 9.1": ["doin"], "2.7 3.2 0.9": ["decamped"], "18.8 7.6 -0.9": ["beeping"], "13.7 13.4 6.3": ["obama"], "14.3 8.4 17.6": ["pug"], "-7.0 6.3 11.5": ["judgeships"], "3.6 10.0 17.4": ["bulkhead"], "9.6 4.7 10.6": ["ashtrays"], "23.5 24.0 23.6": ["serpent"], "7.2 11.7 7.6": ["beatdown"], "-4.4 0.0 10.6": ["endometriosis"], "11.4 11.4 11.1": ["driller"], "7.6 9.4 8.7": ["balm"], "7.4 2.1 11.0": ["bakkie"], "5.4 2.5 13.4": ["lee"], "1.5 22.5 6.2": ["despises"], "-2.6 16.1 3.8": ["misogyny"], "11.9 11.7 8.3": ["uncontrollably"], "5.0 10.5 -3.5": ["overawed"], "3.0 5.7 14.5": ["jung"], "22.8 12.6 7.3": ["corp"], "0.4 0.3 -0.4": ["condense"], "9.6 8.9 7.7": ["displaces"], "12.0 4.1 31.3": ["jellies"], "14.1 16.3 4.4": ["shriek"], "12.7 5.7 4.9": ["rustling"], "-8.5 -3.7 8.4": ["postpartum"], "12.9 12.6 19.2": ["grinders"], "-4.2 5.2 9.8": ["depressive"], "-2.4 17.7 -0.2": ["ultraconservative"], "10.4 -3.8 7.9": ["que"], "4.5 11.7 8.7": ["wails"], "4.7 12.7 0.1": ["missives"], "-0.1 6.9 1.7": ["restful"], "4.2 2.2 2.1": ["miniaturization"], "0.6 19.2 9.4": ["privates"], "7.3 9.6 7.5": ["forges"], "11.4 13.7 26.4": ["condiment"], "3.5 4.9 23.6": ["azaleas"], "6.3 6.9 6.1": ["gf"], "0.2 -0.1 7.8": ["prim"], "-6.8 14.6 7.5": ["bunts"], "-9.1 7.0 4.7": ["educationally"], "2.1 2.0 9.1": ["proffer"], "13.1 -1.5 3.1": ["exp"], "-2.7 7.1 7.3": ["reburied"], "11.5 -2.5 8.2": ["snowballing"], "-4.9 3.9 -5.2": ["perusal"], "7.1 24.0 3.9": ["disorienting"], "-2.6 7.2 43.7": ["hatcheries"], "6.3 8.1 11.9": ["barman"], "3.2 11.6 11.2": ["disenfranchise"], "17.8 -1.9 23.6": ["polystyrene"], "-5.5 9.1 -1.6": ["mufti"], "18.0 5.9 2.8": ["lampposts"], "-7.0 6.3 12.2": ["runoffs"], "26.3 5.0 13.7": ["bellwethers"], "-8.3 -2.7 9.3": ["repave"], "10.2 1.9 3.3": ["unblock"], "12.7 7.6 34.9": ["gourd"], "-0.7 0.3 12.6": ["bangles"], "6.1 5.6 6.7": ["frivolity"], "5.5 -1.1 11.0": ["untraded"], "-3.4 1.8 4.4": ["reevaluated"], "-0.5 4.6 7.0": ["epidemiologists"], "3.5 17.2 9.5": ["splinters"], "-0.3 9.3 8.4": ["romanticism"], "8.1 3.0 -1.6": ["printouts"], "4.5 -0.2 -1.2": ["imprimatur"], "8.4 -4.5 3.3": ["harkens"], "6.7 3.3 12.6": ["snooty"], "3.5 5.1 8.1": ["worksheets"], "2.0 14.5 14.8": ["hai"], "-0.4 6.9 -0.5": ["advantaged"], "15.5 1.4 19.0": ["nibbled"], "22.6 -2.4 10.6": ["swathed"], "-7.0 2.8 -5.9": ["acknowledgments"], "2.2 10.8 4.7": ["categorizing"], "9.3 8.6 23.8": ["bony"], "-8.4 7.2 4.7": ["monastic"], "5.4 -3.4 7.3": ["regaled"], "6.4 11.4 37.4": ["orcas"], "-11.8 7.5 -0.1": ["reappraisal"], "-9.8 9.7 2.7": ["prioritizes"], "8.0 0.9 10.0": ["meshes"], "9.0 2.9 8.6": ["supermodels"], "0.4 12.9 2.2": ["reacquainted"], "-0.0 0.1 3.2": ["dvd"], "2.2 0.2 4.5": ["bioethanol"], "3.3 2.5 5.1": ["murkier"], "1.4 -3.7 2.3": ["inhalers"], "20.4 17.2 5.4": ["hissing"], "10.4 7.1 17.7": ["skateboarder"], "0.2 3.1 13.5": ["festivity", "boutiquey"], "-6.6 14.8 -4.6": ["abolitionist"], "-1.2 2.7 8.7": ["strokeplay"], "0.5 15.6 3.5": ["polemic"], "1.7 15.6 7.7": ["unexplainable"], "5.7 10.3 -0.5": ["copycats"], "14.0 9.6 10.5": ["tangling"], "0.1 8.1 9.6": ["tho"], "-7.7 14.3 23.8": ["salting"], "11.3 15.1 7.5": ["whined"], "0.9 8.7 0.2": ["recommit"], "0.9 3.1 22.7": ["poinsettias"], "6.5 21.7 4.8": ["telegraphed"], "9.4 13.7 11.4": ["millisecond"], "6.8 10.8 1.9": ["readout"], "4.5 -0.6 10.8": ["flutes"], "-1.6 12.3 2.1": ["resourcing"], "-0.2 7.5 4.4": ["sprains"], "7.1 18.5 11.6": ["slyly"], "6.6 18.9 4.3": ["demonization"], "1.1 16.5 5.0": ["tellingly"], "-6.0 10.1 15.3": ["ores"], "9.5 9.4 7.0": ["collider"], "-7.1 6.4 0.8": ["pentathlon"], "-2.2 5.7 2.5": ["quarterbacked"], "-0.7 22.0 10.2": ["antiterrorism"], "12.9 8.8 0.8": ["countersuit"], "22.2 6.4 0.6": ["superhighway"], "12.3 8.6 5.1": ["ditto"], "-5.7 -0.2 8.1": ["headteachers"], "8.0 15.6 4.5": ["whence"], "-0.7 16.3 7.6": ["selfishly"], "8.3 5.9 16.5": ["stoner"], "13.7 19.8 16.4": ["burrows"], "0.0 5.4 8.4": ["governorate"], "5.7 9.4 10.8": ["suburbanites"], "4.4 7.7 11.1": ["screamer"], "-7.3 17.3 1.6": ["egress"], "6.9 1.7 0.4": ["extender"], "9.6 10.7 26.7": ["discards"], "5.2 10.1 7.8": ["duchess"], "3.8 -4.2 11.1": ["galas"], "7.6 5.0 5.7": ["wrung"], "6.5 5.3 14.9": ["pouting"], "1.3 1.4 17.2": ["racino"], "2.7 16.8 3.0": ["oneness"], "-0.8 9.6 4.2": ["kindest"], "-0.9 7.0 4.3": ["liquidations"], "-3.3 11.3 4.5": ["cytokines"], "-4.8 1.9 5.1": ["headmistress"], "0.4 1.5 43.8": ["fillets"], "22.8 15.0 11.2": ["cityscape"], "14.3 15.4 19.6": ["spawns"], "-0.4 14.1 1.8": ["humanism"], "18.9 -2.4 9.4": ["meteoric"], "16.1 9.3 4.7": ["unfurl"], "6.1 12.8 10.3": ["adjuster"], "7.8 4.9 8.0": ["principality"], "11.4 10.0 5.9": ["wrenched"], "8.7 2.9 -1.6": ["undervalues"], "5.6 8.6 7.4": ["bicep"], "10.3 14.8 11.6": ["finders"], "-1.5 9.3 0.9": ["distinguishable"], "11.9 13.5 15.9": ["submerge"], "7.1 2.0 22.3": ["shag"], "-8.8 6.2 0.7": ["excerpted"], "-3.6 7.8 5.1": ["chronologically"], "5.1 12.5 10.2": ["comeuppance"], "13.5 9.8 24.9": ["fleshy"], "-6.9 4.0 5.3": ["annotated"], "4.9 3.0 72.3": ["scallop"], "7.3 6.0 7.2": ["groundskeeper"], "0.3 19.3 10.2": ["powerlessness"], "10.9 16.1 28.1": ["cicadas"], "11.1 -1.3 4.2": ["wows"], "21.0 11.1 7.9": ["moonwalk"], "7.2 6.3 3.9": ["blacklisting", "commiserated"], "18.0 16.6 9.6": ["chieftain"], "5.3 4.6 7.7": ["sis"], "-0.5 3.6 6.8": ["rankles"], "3.6 11.0 10.2": ["ocular"], "22.6 13.2 11.2": ["hoards"], "9.6 6.1 3.2": ["mints"], "16.2 9.2 15.9": ["pebble"], "-1.4 19.4 7.2": ["misjudgment"], "-4.1 18.3 9.2": ["proportionality"], "1.2 10.3 10.6": ["snort"], "10.1 6.6 19.0": ["unevenly"], "8.5 10.8 5.3": ["uneconomic"], "-1.9 3.7 8.2": ["quarreled"], "11.2 5.5 10.5": ["crests"], "4.6 10.1 2.4": ["refreshes"], "2.4 16.3 -3.7": ["mobilizes"], "3.1 5.7 5.4": ["weightings"], "-1.8 24.6 2.7": ["decisiveness"], "2.7 5.9 10.5": ["nighter"], "-4.4 16.6 6.9": ["talkers"], "6.9 14.6 15.5": ["softest"], "-0.5 -6.1 1.5": ["medial"], "6.7 17.1 4.5": ["afflictions"], "6.0 8.7 8.7": ["undercarriage"], "14.8 11.7 5.2": ["lurked"], "-2.4 5.6 1.2": ["contraindicated"], "10.4 18.2 5.7": ["agitator"], "2.2 -0.1 15.6": ["pajama"], "-0.1 12.4 6.0": ["cooped"], "7.5 6.8 8.5": ["lumping"], "3.6 9.7 10.9": ["dwindles"], "3.9 4.0 11.5": ["surtax", "geosequestration"], "4.3 7.4 2.7": ["dissed"], "7.5 2.6 14.7": ["flowered"], "10.3 18.1 7.3": ["gulag"], "0.4 5.8 17.8": ["naturalists"], "7.4 9.6 6.6": ["undignified"], "5.2 9.2 17.9": ["matrimony"], "18.5 15.5 10.9": ["caverns"], "1.4 2.9 8.0": ["excised"], "3.7 1.0 0.3": ["antecedents"], "-0.7 2.3 16.1": ["ovarian"], "9.0 -0.9 1.0": ["dozed"], "4.5 22.3 9.3": ["pessimist"], "-9.4 8.1 12.4": ["minicamps"], "2.0 9.6 1.3": ["quantifies"], "8.3 17.1 4.6": ["romancing"], "-8.9 4.0 18.6": ["billet"], "1.7 12.4 7.1": ["procrastinate"], "5.9 14.6 17.3": ["marshy"], "11.5 5.2 13.4": ["hippy"], "14.4 20.9 17.8": ["bugger"], "-3.9 14.4 0.3": ["unselfishly"], "3.5 0.6 -3.5": ["fora"], "12.2 7.7 7.8": ["newsreader"], "5.6 9.3 30.3": ["pinks"], "17.1 2.8 20.9": ["licorice"], "8.6 14.9 2.3": ["sacrilege"], "-3.6 -7.5 3.4": ["emceed"], "-1.9 14.1 11.3": ["legislatively"], "10.9 10.1 9.4": ["jettisoning"], "6.7 32.7 1.8": ["inimical"], "-4.7 23.7 6.3": ["irreconcilable"], "15.7 7.2 11.5": ["tramp"], "-1.6 15.5 12.4": ["condescension"], "18.6 -0.1 12.0": ["slathered"], "4.1 33.1 4.8": ["despotic"], "9.7 12.9 6.2": ["shrieked"], "9.8 7.9 10.1": ["algorithmic"], "5.9 13.2 2.1": ["locus"], "1.8 10.5 -1.7": ["heatstroke"], "-2.6 8.1 20.4": ["forestland"], "7.9 3.5 3.7": ["twentieth"], "5.4 5.2 4.1": ["pastiche"], "-2.2 7.4 3.1": ["earnestness"], "13.4 8.7 12.1": ["prospectors"], "16.4 15.6 0.8": ["squint"], "0.5 3.2 -1.5": ["niggles"], "4.0 -6.8 13.7": ["peter"], "8.0 15.3 -0.1": ["unenviable"], "17.6 3.7 4.8": ["chugged"], "6.4 6.7 10.1": ["celebrants"], "7.5 17.7 -1.5": ["combats"], "16.2 14.7 5.8": ["roundly"], "0.3 4.8 3.9": ["appended"], "-5.2 4.3 -2.6": ["architected"], "4.4 -3.5 21.2": ["piglets"], "6.1 0.6 23.7": ["pepperoni"], "-0.9 2.4 0.9": ["reproducible"], "4.5 0.5 12.0": ["ding"], "8.3 9.2 4.8": ["heckuva"], "-1.2 1.6 9.3": ["preparers"], "-0.2 13.1 9.3": ["outdoorsman"], "3.9 15.1 7.7": ["gossiping"], "10.2 10.1 14.3": ["thievery"], "6.7 7.4 19.4": ["riverbanks"], "5.3 6.2 4.4": ["hydrology"], "-1.2 11.9 22.6": ["dispersant"], "4.0 7.4 3.8": ["reprogram"], "6.8 8.7 6.7": ["btw"], "1.5 16.5 6.4": ["exponent"], "7.4 7.2 5.2": ["materializing"], "15.6 17.3 27.2": ["falcon"], "-5.6 14.4 -4.1": ["internalize"], "-0.8 3.7 5.1": ["paisa"], "9.4 9.6 12.2": ["predilection"], "-12.4 9.0 1.4": ["salutatorian"], "2.6 8.7 2.5": ["cannibalize"], "14.1 10.8 20.4": ["snowflake"], "7.9 -6.8 -0.0": ["okayed"], "9.0 0.8 11.8": ["tainting"], "4.4 17.0 8.4": ["winks"], "8.2 10.7 12.5": ["backwaters"], "5.6 2.6 1.6": ["optionally"], "3.7 15.7 3.8": ["hypothetically"], "14.4 2.9 12.9": ["bookends"], "0.3 9.0 6.9": ["essayist"], "7.8 2.5 16.6": ["botulism"], "0.9 8.0 -0.3": ["decontaminated"], "5.5 5.8 13.2": ["etchings"], "-1.5 8.7 4.3": ["chaste"], "-5.0 2.0 3.2": ["abeyance"], "-7.8 4.9 11.9": ["telework"], "-7.3 1.1 2.1": ["republication"], "15.1 8.1 6.3": ["multitouch"], "2.7 14.5 8.8": ["immemorial"], "5.9 2.0 14.1": ["tickling"], "-3.2 14.9 1.8": ["womanizer"], "0.6 2.0 19.1": ["rapeseed"], "13.7 24.9 10.8": ["meanest"], "0.0 13.9 4.0": ["possessive"], "-1.4 2.6 0.5": ["intravenously"], "-4.5 1.4 8.6": ["curatorial"], "10.8 13.6 10.9": ["submerging"], "12.0 -2.1 7.9": ["nosedived"], "2.5 5.6 8.8": ["bestiality"], "-2.2 7.9 4.2": ["reactivation"], "4.5 15.7 6.7": ["transcending"], "-9.2 7.2 -2.3": ["excusing"], "6.3 7.6 7.9": ["kink"], "-3.0 4.8 0.2": ["audiobooks"], "20.7 29.9 7.0": ["bogeyman"], "-6.9 -3.2 3.6": ["anecdotally"], "-12.4 -0.1 10.3": ["prekindergarten"], "18.1 6.3 11.8": ["lazily"], "2.8 10.5 2.3": ["taxiing"], "-2.6 3.6 2.5": ["consignor"], "12.4 4.6 0.0": ["parodied"], "-1.4 2.4 10.5": ["tannins"], "10.7 -0.8 7.0": ["oozed"], "-2.2 9.9 -3.8": ["rehashing"], "-8.8 6.5 -1.0": ["drafters"], "9.0 7.5 1.6": ["airbrushed"], "-1.9 12.5 8.0": ["federalist"], "9.2 1.9 11.1": ["datacentre"], "-12.9 7.7 -1.6": ["averred"], "1.5 4.6 17.1": ["swum"], "13.0 1.0 -0.8": ["ousts"], "11.4 7.1 11.9": ["weightless"], "12.3 1.3 15.9": ["wispy"], "12.2 6.5 6.8": ["fitful"], "0.4 0.1 1.7": ["overdosing"], "1.1 10.1 4.8": ["fantasized"], "11.3 2.8 9.7": ["wriggled"], "2.3 10.0 5.8": ["conductivity"], "11.9 18.8 7.6": ["storehouse"], "8.4 8.9 6.1": ["misspelling"], "2.4 4.3 27.6": ["curries"], "2.9 14.4 6.5": ["meritocracy"], "2.5 11.6 8.3": ["observatories"], "5.6 1.2 20.0": ["phentermine"], "3.9 2.9 5.4": ["typewriters"], "8.4 17.7 6.1": ["conceals"], "3.8 6.5 8.3": ["ritualistic"], "10.4 5.2 0.2": ["priming"], "4.9 5.3 11.3": ["transgenic"], "15.1 23.0 -1.0": ["squinting"], "9.7 4.6 5.4": ["slackening"], "11.5 17.3 6.4": ["whiners"], "3.9 3.4 13.4": ["spliced"], "10.1 0.8 3.1": ["parastatal"], "5.8 16.3 9.3": ["bounties"], "3.1 5.1 30.3": ["tubers"], "-1.8 16.0 16.7": ["mace"], "4.6 7.1 16.5": ["tacks", "pericyte"], "4.8 11.0 13.7": ["bunks"], "-8.4 10.6 2.1": ["instills"], "-0.2 6.3 14.8": ["whitewater"], "2.1 6.1 6.1": ["sympathetically"], "-6.9 3.0 6.0": ["acclamation"], "6.0 11.5 11.6": ["punditry"], "11.4 15.3 -0.3": ["zigzag"], "1.4 24.8 8.7": ["obstructionist"], "-3.1 2.0 3.7": ["laxity"], "5.7 15.9 0.4": ["firebombs"], "7.7 12.1 0.5": ["entreaties"], "1.6 13.8 14.9": ["irradiated"], "-4.3 3.4 4.9": ["delegating"], "2.5 -3.0 1.8": ["tion"], "-10.2 1.8 0.7": ["exhume"], "0.1 9.2 4.4": ["unreadable"], "13.2 7.4 11.2": ["zebras"], "2.6 10.0 8.3": ["philandering"], "3.8 1.6 -2.2": ["roughshod"], "7.6 5.7 10.5": ["receptacle"], "12.6 -4.1 2.8": ["incl"], "5.2 4.8 7.0": ["serendipitous"], "9.2 3.1 6.0": ["twentysomething"], "3.7 5.6 18.5": ["minced"], "1.6 3.4 1.5": ["hassled"], "7.1 13.7 4.2": ["exclusionary"], "9.7 14.0 13.1": ["unadulterated"], "0.7 11.0 10.0": ["germinate"], "3.9 6.8 5.1": ["hydrate"], "7.3 1.0 3.7": ["torchbearers"], "4.8 10.6 5.2": ["hackneyed"], "-6.3 -0.8 -4.6": ["gynecological"], "4.1 5.2 6.6": ["locksmith"], "-1.1 12.8 11.6": ["segregationist"], "6.7 5.5 6.1": ["dampens"], "-9.2 8.3 8.9": ["upazila"], "1.1 -2.0 12.7": ["outplacement"], "7.5 6.4 1.4": ["grooving"], "8.8 12.0 5.9": ["addicting"], "4.1 13.8 8.7": ["anointing"], "6.0 15.8 5.5": ["redistributing"], "-3.6 11.7 11.5": ["gritting"], "11.2 5.0 19.0": ["orangutan"], "6.7 2.8 7.6": ["eccentricity"], "16.7 20.3 32.5": ["amphibian"], "13.3 -0.2 -0.8": ["briefcases"], "2.3 6.7 0.9": ["faulting"], "12.5 11.8 25.6": ["pythons"], "-6.7 25.0 1.4": ["apostasy"], "5.2 12.3 22.6": ["pussy"], "12.0 8.6 12.0": ["flayed"], "9.6 21.2 12.1": ["jackass"], "2.0 8.9 11.0": ["inflection"], "-5.6 8.6 6.9": ["touchbacks"], "6.7 13.2 7.0": ["specious"], "12.3 26.3 3.8": ["terrify"], "-2.0 5.0 10.3": ["chickenpox"], "2.7 12.8 8.1": ["adjusters"], "-10.9 9.2 6.9": ["returnee"], "4.9 5.7 2.2": ["gyroscopes"], "2.0 6.1 9.9": ["greenbelt"], "1.8 4.1 -0.3": ["tidying"], "4.4 4.1 10.5": ["extrusion"], "1.2 17.6 21.9": ["fertilizing"], "5.3 8.0 2.2": ["fascinates"], "11.0 24.4 15.6": ["castaways"], "7.4 15.5 10.0": ["undergrowth"], "7.8 19.0 4.8": ["perimeters"], "-8.2 2.4 9.5": ["originations"], "0.3 6.5 5.8": ["registrant"], "1.9 8.9 -1.6": ["technocrat"], "-2.1 12.6 5.9": ["sob"], "3.1 -0.2 2.8": ["naproxen"], "15.3 26.4 10.3": ["mortals"], "7.4 19.5 9.8": ["detested"], "1.7 -1.5 18.2": ["unprocessed"], "1.4 11.0 10.6": ["caloric"], "7.0 -1.6 5.6": ["scandalized"], "-0.4 12.6 22.7": ["frosts"], "3.5 5.3 31.0": ["tusks"], "2.5 3.2 6.2": ["tracksuit"], "15.0 7.2 10.4": ["multilayered"], "11.8 -3.4 12.6": ["sizzled"], "17.3 17.2 10.3": ["kingpins"], "-5.7 5.4 9.2": ["tempos"], "4.0 12.9 6.3": ["riposte"], "5.8 13.7 29.8": ["robins"], "-0.6 12.0 31.1": ["crappies"], "5.2 20.3 17.2": ["underhand"], "9.2 1.1 6.6": ["ch"], "7.5 10.0 4.8": ["swifter"], "-0.5 1.0 0.3": ["leakages"], "5.6 6.8 -3.2": ["rectifying"], "4.7 6.4 14.1": ["unfunny"], "9.3 6.6 9.0": ["concocting"], "11.1 12.7 16.8": ["sagebrush"], "-0.3 22.0 3.2": ["ammunitions"], "5.0 10.6 34.2": ["mangrove"], "-3.1 9.9 1.7": ["graveside"], "7.6 15.6 25.8": ["chartreuse"], "-1.6 11.3 7.8": ["humanistic"], "-2.4 25.4 -0.4": ["conspiratorial"], "11.9 1.1 1.3": ["reverberations"], "14.9 19.1 8.8": ["proclivity"], "1.5 7.5 10.9": ["walkoff"], "9.4 22.5 1.9": ["invisibility"], "1.7 16.6 10.1": ["deflections"], "0.5 11.7 -1.9": ["demobilized"], "-6.7 7.6 20.3": ["cultivars"], "-1.4 0.6 4.9": ["videographers"], "5.8 4.2 2.2": ["unbundled"], "5.2 12.1 15.5": ["herders"], "5.4 22.3 6.1": ["theocratic"], "8.0 12.0 6.5": ["hemispheric"], "4.9 10.4 -0.7": ["drowsiness"], "-7.1 10.2 8.3": ["excepted"], "1.9 3.6 4.5": ["brassy"], "13.1 -0.2 19.5": ["woolly"], "1.1 6.9 7.6": ["muffler"], "3.7 1.5 0.9": ["squirmed"], "0.8 8.1 2.1": ["powerplant"], "9.9 4.9 22.0": ["nibbles"], "6.9 2.3 6.8": ["grinded"], "13.4 15.0 7.2": ["unmitigated"], "5.2 11.8 5.7": ["myopia"], "2.6 9.5 20.8": ["hardwoods"], "22.2 6.8 8.1": ["toehold"], "6.1 10.4 11.1": ["windpipe"], "9.3 38.0 5.6": ["tormentors"], "6.0 12.5 7.7": ["gallops"], "9.2 12.7 20.6": ["mistletoe"], "16.2 10.0 4.4": ["america"], "10.4 8.2 6.3": ["trots"], "6.5 1.4 25.0": ["couscous"], "18.4 2.9 14.3": ["starry"], "-0.9 -3.1 -0.4": ["maj"], "7.9 1.5 5.6": ["cascaded"], "17.9 11.2 8.9": ["snobs"], "8.1 5.4 5.4": ["huffed"], "3.1 9.0 8.3": ["bandanna"], "6.9 4.9 10.1": ["loosens"], "20.0 13.0 0.1": ["topples"], "10.9 13.6 0.3": ["borderless"], "-5.6 7.2 12.3": ["reversion"], "2.4 12.6 -1.9": ["initiator"], "-3.0 2.8 20.1": ["snowshoeing"], "-1.0 13.1 12.9": ["gangsta"], "12.9 13.2 6.1": ["lifelines"], "-5.5 12.0 -2.5": ["epilogue"], "12.7 -0.4 17.6": ["piggy"], "-3.4 5.2 0.7": ["holier"], "7.9 9.3 4.5": ["harmoniously"], "11.5 1.3 1.8": ["relocates"], "-3.6 7.4 7.9": ["bitchy"], "5.6 14.6 5.9": ["boastful"], "12.6 26.9 13.8": ["brutish"], "0.1 10.4 12.1": ["overcoat"], "10.4 5.9 7.6": ["motley"], "-0.3 4.1 3.7": ["refrigerant"], "1.3 4.2 11.9": ["stepsister"], "1.7 7.0 8.7": ["rues"], "7.2 3.4 1.7": ["gloomier"], "10.3 14.9 8.1": ["somersault"], "-2.7 -0.3 0.8": ["overcorrected"], "-5.4 5.2 -1.7": ["solicits"], "12.0 16.4 8.5": ["ravage"], "-10.8 -1.7 -1.3": ["gastroenterology"], "14.3 10.9 62.0": ["prawn"], "-0.8 4.7 7.8": ["unrealistically"], "1.8 2.2 10.9": ["skews"], "13.5 2.8 15.5": ["peppermint"], "5.9 6.9 11.1": ["fussing"], "-8.8 7.4 -1.0": ["neurosurgeons"], "-1.1 9.7 26.7": ["seedling"], "7.3 2.7 4.3": ["rarefied"], "-0.2 -7.2 10.2": ["bimonthly"], "-2.0 14.9 43.2": ["bluefish"], "-0.9 8.1 10.3": ["terrifically"], "2.7 15.2 8.0": ["encampments"], "-2.4 4.7 4.0": ["dwelt"], "15.9 2.9 5.1": ["ambled"], "0.7 2.7 -0.5": ["accrediting"], "8.2 12.2 10.0": ["pathetically"], "3.1 7.6 6.1": ["definately"], "14.4 18.3 31.0": ["boar"], "20.9 19.1 11.3": ["profiteers"], "16.6 10.2 15.2": ["screech"], "13.0 16.1 3.4": ["roams"], "7.8 13.9 10.9": ["speculator"], "6.8 -0.5 -0.5": ["endow"], "-5.1 15.4 4.9": ["polarize"], "7.8 10.4 1.9": ["lookup"], "-8.0 8.7 2.6": ["callup"], "-7.6 11.1 12.9": ["coxswain"], "2.1 11.9 -3.7": ["unencrypted"], "11.8 14.1 4.4": ["besotted"], "-1.3 11.3 3.5": ["forgives", "truces"], "8.2 -0.3 36.2": ["chorizo"], "2.0 7.3 2.7": ["housecleaning"], "0.1 7.4 8.7": ["prelim", "indefeasible"], "9.1 18.4 4.6": ["embargoes"], "36.8 0.7 14.0": ["supersized"], "3.2 -0.2 6.8": ["reliefs"], "-4.4 11.5 5.8": ["generalization"], "8.7 6.7 8.4": ["upending"], "-9.8 15.7 11.4": ["glyphosate"], "19.6 0.8 1.1": ["marquees"], "6.8 7.7 4.1": ["bedlam"], "7.8 4.7 2.4": ["babbling"], "7.0 5.0 9.9": ["sinkholes"], "24.6 18.6 16.0": ["rapacious"], "10.4 10.7 14.1": ["shoplifter"], "-2.8 -2.1 3.8": ["dockets"], "20.5 4.2 17.0": ["spongy"], "4.8 7.2 5.5": ["uninstall"], "-3.7 5.8 6.3": ["overdrawn"], "5.4 4.6 7.0": ["tabular"], "16.0 5.7 11.6": ["pudgy"], "-8.2 0.8 4.9": ["refinancings"], "-3.6 2.6 3.9": ["tapings"], "9.8 16.3 27.4": ["tom"], "23.3 10.0 18.7": ["caveman"], "-8.7 19.7 -0.6": ["untruthful"], "13.3 16.1 8.4": ["pirating"], "-0.7 6.8 10.6": ["neuronal"], "4.5 30.9 0.8": ["torturers"], "-2.7 1.0 8.2": ["methotrexate"], "3.6 5.8 7.7": ["conferees"], "7.4 11.7 12.0": ["nontoxic"], "-5.6 5.0 -2.6": ["apprise"], "7.6 14.7 -1.0": ["clasped"], "1.8 -0.2 17.2": ["horseracing"], "-0.6 15.7 11.3": ["staph"], "3.4 4.7 2.6": ["readability"], "5.3 25.2 6.2": ["blowback"], "3.0 10.6 5.3": ["gullies"], "10.9 9.7 4.6": ["behinds"], "4.7 6.0 8.9": ["fadeaway"], "-0.9 7.2 6.2": ["songbook"], "4.1 -0.2 9.8": ["limos"], "-0.6 14.9 0.9": ["thankless"], "-16.0 7.4 5.1": ["myeloma"], "4.4 9.1 24.4": ["marshland"], "-3.5 17.0 19.7": ["jueteng"], "12.7 -0.7 0.8": ["overcharges"], "1.0 10.5 -0.8": ["unverified"], "11.3 -1.5 -2.1": ["fiddled"], "-7.3 12.9 -2.0": ["recant"], "21.5 7.1 11.2": ["outsourcer"], "-1.0 24.7 8.3": ["materiel"], "20.0 18.9 10.0": ["astride"], "-5.9 6.6 7.0": ["musicality"], "5.4 1.9 6.1": ["boilerplate"], "9.2 5.4 10.0": ["omega"], "10.3 6.9 15.5": ["cobblestones"], "7.9 9.2 18.2": ["auger"], "8.1 11.8 8.1": ["fulcrum"], "18.3 17.3 17.5": ["perches"], "12.4 18.4 10.6": ["blinks"], "5.0 7.3 14.6": ["bushy"], "-3.1 -5.6 3.7": ["curate"], "-2.4 -4.6 1.6": ["vouched"], "6.3 14.5 4.4": ["blundered"], "29.1 11.7 21.8": ["blobs"], "13.8 1.4 4.7": ["melds"], "-7.2 2.5 10.0": ["reoccurring"], "8.2 6.0 1.4": ["farfetched"], "2.9 4.8 10.0": ["refusals"], "13.8 12.1 8.7": ["clatter"], "3.2 -1.1 3.8": ["biopharmaceuticals"], "1.0 16.5 22.8": ["seaman"], "11.5 10.1 8.1": ["umpteen"], "-4.7 7.3 7.5": ["celibate"], "7.0 -0.6 9.4": ["allotting"], "9.9 8.4 8.7": ["steelworkers"], "20.6 5.7 18.7": ["drooping"], "7.6 9.8 0.9": ["contravenes"], "5.5 4.9 3.0": ["abbreviations"], "7.5 5.9 4.6": ["denoting"], "14.7 34.8 4.9": ["cower"], "2.0 5.5 3.3": ["personals"], "2.4 20.1 3.4": ["conscripts"], "-2.9 10.7 8.3": ["homesickness"], "3.7 10.5 1.5": ["reputational"], "7.6 24.6 4.9": ["preemptively"], "-2.5 9.0 11.4": ["propellant"], "3.3 -2.4 6.0": ["ultrasounds"], "5.5 11.7 3.0": ["stoplights"], "10.6 -0.2 28.3": ["crepe"], "9.5 7.9 4.2": ["spellbound"], "4.3 13.8 7.2": ["pangs"], "6.4 20.3 11.0": ["multiplies"], "14.6 31.7 11.2": ["savages"], "12.8 8.7 15.8": ["paintbrush"], "1.2 7.8 15.2": ["baristas"], "-1.7 21.4 -1.4": ["hardliner"], "9.6 13.7 11.2": ["treetops"], "5.2 7.5 23.7": ["lacquer"], "4.9 3.5 -4.1": ["audiotapes"], "0.8 5.4 5.2": ["accentuates"], "2.3 4.8 25.7": ["wildflower"], "12.5 12.6 11.8": ["seer"], "5.9 -5.7 3.8": ["repackage"], "-2.0 8.9 8.0": ["millisieverts"], "8.9 5.0 3.7": ["preteens"], "2.5 -0.3 3.0": ["clued"], "15.1 18.5 11.5": ["growled"], "1.6 4.0 4.5": ["unbanked"], "6.6 23.4 8.0": ["loathsome"], "9.8 12.1 19.6": ["emperors"], "9.6 4.3 7.4": ["budging"], "3.2 7.0 1.1": ["bonafide"], "-0.1 8.6 3.1": ["baptisms"], "-3.8 20.1 6.8": ["interviewee"], "4.6 9.2 7.8": ["secretion"], "12.1 15.0 4.3": ["urinal"], "-1.8 10.3 4.8": ["bloodline"], "5.9 7.0 11.2": ["soundstage"], "7.2 4.3 5.9": ["undid"], "5.6 4.9 3.6": ["unviable"], "11.7 12.5 4.8": ["subliminal"], "7.1 3.6 1.6": ["joyride"], "5.5 5.2 31.4": ["okra"], "9.2 6.3 -1.0": ["exorcise"], "-0.5 0.5 17.0": ["summery"], "-2.8 6.2 -2.2": ["pressurizing"], "7.1 12.1 9.1": ["sneered"], "-1.7 7.8 3.0": ["fatwas"], "9.7 15.5 -0.5": ["retrograde"], "11.0 5.4 5.4": ["tailwind"], "0.3 3.1 19.6": ["tableware"], "-2.0 -5.8 -2.5": ["voiding"], "3.5 9.6 11.5": ["untracked"], "1.2 6.2 16.6": ["varnish"], "5.9 2.1 4.2": ["bioengineering"], "7.9 7.8 9.2": ["eccentricities"], "11.7 -1.6 11.6": ["potpourri"], "13.5 7.1 9.5": ["wonderment"], "1.8 12.5 16.0": ["almanac"], "13.3 24.7 7.5": ["wrongdoers"], "3.7 -0.4 2.7": ["gravitated"], "-5.7 8.6 9.0": ["monogamous"], "5.7 -7.7 4.1": ["hairdressing"], "10.2 -0.9 27.0": ["mousse"], "16.8 3.7 -0.6": ["flapped"], "7.4 4.5 -1.2": ["commercializes"], "-4.1 -1.8 15.6": ["composted"], "6.6 7.1 3.9": ["excoriated"], "8.5 16.9 8.2": ["thunderbolt"], "27.9 25.6 19.2": ["ogre"], "2.5 -2.3 5.3": ["programing"], "2.9 10.2 -1.2": ["flashpoints"], "1.2 1.3 3.4": ["hotlines"], "6.9 9.1 6.0": ["untaxed"], "24.6 10.7 12.7": ["contraptions"], "8.6 2.6 -0.1": ["emulates"], "18.9 -3.0 16.2": ["fattened"], "-3.4 10.2 0.6": ["pecuniary"], "1.6 7.0 11.9": ["roadmaps"], "17.4 4.7 10.7": ["trippy"], "5.8 7.5 1.0": ["reprogrammed"], "9.3 6.3 25.3": ["morsels"], "3.8 6.4 7.4": ["goalline"], "-1.7 6.8 8.8": ["melancholic"], "7.0 22.2 4.3": ["exterminated"], "-5.2 27.7 6.0": ["aircrew"], "2.0 12.1 25.3": ["snappers"], "10.6 0.1 10.4": ["blah"], "6.7 9.4 11.1": ["ravishing"], "12.6 6.1 10.7": ["preschooler"], "6.4 4.6 3.0": ["geophysicist"], "3.9 7.2 2.4": ["nongovernmental"], "8.2 15.7 4.2": ["annoyances"], "2.6 4.6 3.5": ["reformulated"], "-6.9 12.5 6.8": ["discernment"], "-1.7 7.0 0.4": ["integrative"], "1.9 7.8 7.1": ["nullifying"], "9.8 6.3 2.3": ["stethoscope"], "4.9 7.7 8.3": ["repatriating"], "6.3 9.2 12.2": ["botany"], "5.6 6.6 -1.2": ["compresses"], "-6.1 3.5 -2.4": ["telephoning"], "7.4 9.1 2.7": ["outnumbering"], "12.9 10.1 16.1": ["taxonomy"], "3.2 2.3 6.1": ["ben"], "-2.9 14.8 0.9": ["colonels"], "-4.6 6.9 1.8": ["trysts"], "10.6 6.3 4.6": ["npower"], "3.4 14.2 3.8": ["callousness"], "0.7 3.2 4.7": ["federated"], "-0.7 3.1 10.1": ["ke"], "-0.4 6.3 6.0": ["endocrine"], "0.9 0.4 1.6": ["jaunts"], "-0.5 3.6 16.0": ["outfitters"], "16.3 5.5 2.7": ["prancing"], "-8.3 0.7 2.0": ["bulled"], "0.3 2.6 39.6": ["leeks"], "13.6 0.4 13.3": ["lopped"], "7.8 16.6 5.6": ["winging"], "13.0 5.1 27.0": ["redwood"], "6.0 8.7 5.2": ["discernable"], "-10.0 0.3 6.7": ["alto"], "5.2 7.0 7.9": ["untied"], "6.6 5.3 12.0": ["tucks"], "5.9 11.6 8.9": ["anus"], "-1.7 7.5 23.2": ["reverb"], "-7.6 5.7 1.4": ["biodefense"], "8.8 22.2 22.9": ["badgers"], "15.0 10.8 4.6": ["supplanting"], "5.4 1.2 6.1": ["colic"], "-8.6 12.3 9.5": ["designee"], "12.7 -1.0 2.8": ["bloating"], "7.2 -0.4 1.5": ["sublease"], "-7.3 20.8 9.2": ["patrolmen"], "1.8 12.8 -0.4": ["inflaming"], "1.8 6.9 7.4": ["delinquents"], "-2.6 8.0 8.2": ["melodious"], "-7.3 -0.2 3.3": ["workgroups"], "22.2 -0.6 5.9": ["bil"], "6.9 18.3 11.7": ["buffoon"], "2.3 6.8 5.6": ["gab"], "-0.5 7.2 9.3": ["mayoralty"], "9.1 16.0 9.1": ["universes"], "-1.4 25.3 -0.0": ["peacemakers"], "0.1 1.5 14.0": ["trusses"], "15.7 5.9 8.8": ["bloat"], "-1.6 3.7 0.3": ["activations"], "8.6 16.3 9.5": ["artifice"], "21.3 -11.0 4.0": ["nixes"], "6.2 3.8 11.1": ["synthesizers"], "8.9 27.3 10.1": ["reflexively"], "-4.1 0.9 10.4": ["acrylics"], "3.9 9.0 5.6": ["placebos"], "-5.9 7.2 3.1": ["reprinting"], "12.0 8.3 13.6": ["barging"], "4.3 9.5 6.8": ["pejorative"], "12.0 1.5 2.4": ["pervaded"], "-2.3 5.2 2.5": ["prospectively"], "-3.0 5.1 15.6": ["scuba"], "0.2 8.5 0.2": ["newspersons"], "1.1 8.3 7.5": ["nanowires"], "3.9 4.8 13.5": ["tasters"], "5.6 6.0 11.8": ["overdoing"], "-1.5 -6.8 -4.5": ["homecare"], "14.4 3.2 18.3": ["eucalyptus"], "10.9 9.1 12.2": ["icky"], "-1.8 3.0 -4.7": ["railroaded"], "8.6 6.3 25.0": ["birch"], "0.1 8.9 11.3": ["alms"], "0.1 15.0 -1.2": ["multitask"], "1.1 5.8 1.3": ["primes"], "-3.6 10.9 5.3": ["subtype"], "10.4 -1.6 6.7": ["lugged"], "8.0 3.1 20.4": ["bangers"], "24.8 1.6 13.0": ["headless"], "-3.8 -0.4 5.2": ["arraignments"], "3.3 19.8 9.9": ["autocracy"], "8.1 7.8 1.6": ["blowers"], "2.4 -7.7 1.9": ["sextuplets"], "6.7 5.7 16.8": ["calypso"], "6.5 10.6 8.4": ["perversely"], "2.8 13.5 9.9": ["beret"], "0.9 9.6 8.2": ["abdicate"], "3.5 2.0 8.7": ["sterility"], "2.7 -4.0 -4.0": ["initialed"], "15.2 7.4 7.7": ["leapfrogging"], "0.4 7.4 1.7": ["gametime"], "2.3 -1.0 4.0": ["repurposing"], "-2.8 7.1 0.1": ["prosecutes"], "0.0 4.8 -1.6": ["distill"], "5.4 14.0 1.6": ["dissing"], "15.6 24.2 5.2": ["obliterating"], "-1.7 4.8 15.0": ["cysts"], "-5.0 2.3 7.3": ["brownfields"], "-0.8 7.1 0.4": ["lewdness"], "-6.0 -8.5 6.5": ["retesting"], "6.5 6.8 17.0": ["rickshaws"], "-2.6 8.8 8.4": ["theorize"], "12.9 4.6 5.0": ["enclosing"], "6.6 17.0 16.5": ["aphrodisiac"], "9.3 13.6 1.5": ["marshalling"], "5.6 16.5 9.7": ["motioning"], "13.7 34.8 7.0": ["vanquish"], "10.4 11.2 9.7": ["lovebirds"], "5.1 9.9 14.0": ["sitters"], "10.4 2.3 7.9": ["touchscreens"], "2.3 5.5 15.0": ["ender"], "-1.2 3.5 11.1": ["sweatpants"], "6.8 12.8 -3.7": ["pacesetters"], "-7.5 12.4 3.7": ["deviating"], "9.2 5.3 6.6": ["apropos"], "4.8 23.8 9.0": ["obstinate"], "3.8 3.7 9.5": ["sleepovers"], "14.1 9.0 9.6": ["shuddered"], "13.3 17.9 6.2": ["annoyingly"], "-3.7 3.0 7.0": ["governorates"], "11.0 9.5 18.3": ["superstructure"], "2.6 25.2 10.6": ["retardant"], "16.2 11.3 3.4": ["invents"], "10.7 8.3 16.3": ["baboons"], "7.5 2.9 2.4": ["diodes"], "7.5 1.5 2.4": ["fascia"], "9.8 2.3 6.9": ["outweighing"], "6.1 2.3 10.3": ["squatted", "yuhn"], "15.7 10.5 9.3": ["workman"], "4.0 8.1 13.0": ["morose"], "-4.7 17.4 4.7": ["appellation"], "11.6 1.9 10.9": ["velodrome"], "3.0 3.0 7.4": ["bravura"], "20.8 11.4 6.5": ["diagonally"], "7.3 0.9 1.5": ["hullabaloo"], "8.5 11.6 17.4": ["pacific"], "-2.9 13.9 0.7": ["cloture"], "10.0 14.8 32.3": ["seafaring"], "-3.0 1.9 5.0": ["specializations"], "9.2 14.6 23.2": ["coves"], "13.3 12.3 8.3": ["easel"], "0.4 -1.8 7.1": ["mcg"], "8.4 7.1 1.6": ["fascinate"], "-7.5 9.0 9.5": ["mics"], "13.2 13.7 7.3": ["hypnotized"], "1.4 9.6 18.5": ["flavorings"], "3.7 11.2 -0.8": ["aberrant"], "0.9 3.6 -1.1": ["saloons"], "5.8 1.4 20.2": ["hula"], "-2.8 9.6 4.8": ["alternator"], "-2.0 3.8 5.4": ["microfilm"], "9.8 24.3 9.7": ["immutable"], "7.1 -7.2 6.7": ["tussled"], "0.1 2.1 9.3": ["bindings"], "4.6 13.2 11.7": ["reassemble"], "9.9 2.4 22.6": ["tripe"], "4.3 2.4 6.2": ["rumpled"], "-7.6 11.2 8.0": ["regionalism"], "2.0 12.5 6.6": ["disorganization"], "1.3 13.1 -0.7": ["internationalist"], "5.6 9.0 -0.3": ["sildenafil", "marshalls"], "-4.5 1.5 2.5": ["reminiscences"], "4.0 6.6 11.2": ["bathhouse"], "-1.0 6.2 6.3": ["silencers"], "-9.3 13.6 3.4": ["repeaters"], "12.4 -0.1 3.9": ["reals"], "-3.1 9.0 10.5": ["subdivide"], "22.3 3.6 13.8": ["panoply"], "2.6 16.2 16.1": ["barb"], "-1.4 -3.5 -4.8": ["interning"], "6.6 4.8 4.5": ["coda"], "15.3 -2.2 -0.6": ["toted"], "0.0 17.9 11.7": ["begets"], "23.7 17.3 12.8": ["appendage"], "-2.0 14.9 4.9": ["ablation"], "23.4 21.4 23.7": ["scorpions"], "8.6 8.2 5.0": ["gamma"], "7.8 7.7 6.4": ["peeping"], "8.5 20.1 18.4": ["triad"], "3.8 8.9 2.3": ["jogs"], "-3.0 3.2 8.2": ["helming"], "-1.1 1.1 1.1": ["chapels"], "0.8 13.5 6.7": ["atrophy"], "-1.4 10.6 -0.1": ["praiseworthy"], "14.9 10.5 4.9": ["beeps"], "1.7 23.1 6.4": ["isolationism"], "4.7 9.2 4.0": ["hogwash"], "1.2 -1.3 8.7": ["dietician"], "-0.9 1.5 13.3": ["sutures"], "13.1 -3.7 -1.8": ["pricetag"], "-0.9 7.4 8.1": ["aspartame"], "-4.7 17.6 16.8": ["midshipmen"], "-1.3 -3.9 2.5": ["farewells"], "-3.3 5.8 9.3": ["nightspots"], "5.0 17.8 -1.9": ["denigrated"], "-1.4 3.0 3.0": ["bookish"], "6.7 6.2 6.5": ["asterisks"], "26.7 11.1 22.0": ["unicorn"], "-1.6 5.1 32.4": ["apricots"], "15.7 10.1 27.0": ["lotus"], "-0.2 13.1 0.8": ["evangelization"], "4.3 15.9 -2.0": ["heretical"], "10.1 13.8 10.2": ["thrusters"], "-1.7 15.9 0.8": ["prophecies"], "-5.4 2.1 9.0": ["oboe"], "6.1 4.1 8.5": ["slammer"], "2.0 13.3 10.2": ["delimitation"], "6.1 4.6 13.4": ["farmworker"], "13.3 14.3 3.0": ["hitmen"], "14.0 6.1 10.7": ["squealed"], "20.6 8.0 12.8": ["brawny"], "2.0 3.0 14.3": ["dwt"], "12.3 10.9 14.4": ["jerking"], "10.5 20.0 10.8": ["gutless"], "-14.2 4.9 -1.8": ["reoffend"], "-1.2 -1.5 13.4": ["centenarians"], "20.5 16.8 10.1": ["visage"], "6.8 2.6 4.4": ["tussles"], "-7.2 8.7 -0.7": ["promulgate"], "5.0 6.6 0.9": ["equivalence"], "12.3 8.7 16.1": ["greenbacks"], "1.5 10.4 47.7": ["shrimping"], "11.9 7.3 5.8": ["unconsolidated"], "7.3 15.7 0.6": ["decoded"], "7.6 2.6 11.7": ["cryogenic"], "6.8 0.9 5.3": ["quilted"], "9.3 19.5 10.9": ["heckler"], "-1.3 7.4 8.3": ["bridle"], "3.0 13.8 9.1": ["antimatter"], "10.7 12.9 3.6": ["snuggle"], "8.0 4.3 8.7": ["urbanites"], "-6.8 3.8 8.9": ["chloride"], "18.1 4.2 7.1": ["doodle"], "0.3 18.6 11.8": ["healers"], "-4.9 13.0 0.5": ["disharmony"], "0.3 2.2 21.6": ["ovary"], "-3.8 0.3 10.6": ["shawls"], "1.7 20.3 16.2": ["upwind"], "8.5 3.7 9.3": ["upholstered"], "12.6 9.2 7.6": ["punchless"], "24.7 20.9 12.8": ["goddamn"], "16.7 14.7 30.9": ["hummingbird"], "-2.6 9.6 2.5": ["disregards"], "-3.9 -0.0 -3.0": ["bussed"], "8.1 1.2 5.4": ["ledgers"], "-9.4 11.7 27.7": ["wintering"], "1.5 7.3 3.6": ["prayerful"], "2.2 10.9 11.0": ["wordplay"], "-5.3 12.0 -2.8": ["draftee"], "-2.2 5.5 4.4": ["particulate"], "6.8 31.4 13.5": ["archer"], "0.1 5.1 -0.7": ["collate"], "-2.4 -0.5 14.9": ["oilseed"], "7.5 12.2 14.8": ["pap"], "0.4 4.7 11.1": ["probiotic"], "6.1 6.5 5.7": ["iconoclastic"], "-8.3 5.5 19.3": ["silage"], "-3.0 7.2 7.0": ["communes"], "-3.9 6.8 0.7": ["cryptography"], "-0.6 13.0 8.4": ["firehouses"], "11.4 8.3 2.5": ["gooders"], "7.4 14.4 5.1": ["seducing"], "6.7 14.8 4.7": ["antisocial"], "5.5 6.6 38.2": ["dockside"], "12.7 13.6 8.7": ["hinterlands"], "6.8 0.8 -3.9": ["extol"], "8.4 -0.4 6.3": ["doctoring"], "-1.2 2.1 5.5": ["tics", "skus"], "7.7 5.4 -2.2": ["hypersensitivity"], "-0.3 6.2 11.2": ["bossy"], "-0.7 8.0 7.6": ["intrastate"], "9.4 9.0 7.4": ["pilfering"], "17.7 4.5 5.3": ["chug"], "9.5 3.0 9.2": ["morphology"], "-1.9 13.6 2.2": ["disinfectants"], "8.0 8.1 36.6": ["sauteed"], "11.7 7.4 3.4": ["whooped"], "11.8 1.2 13.4": ["sawn"], "-0.3 17.3 8.1": ["rubric"], "4.7 3.3 9.2": ["carload"], "12.8 8.1 6.9": ["babble"], "2.5 -1.7 9.2": ["milligram"], "11.8 6.1 12.2": ["recoiled"], "-1.9 8.3 -3.4": ["eulogies"], "9.9 18.8 4.4": ["trafficker"], "-2.9 7.4 0.3": ["aberrations"], "3.8 15.8 14.4": ["helmsman"], "7.2 16.7 15.5": ["verbs"], "8.9 -1.0 14.2": ["smidgen"], "9.4 12.7 7.7": ["fantasizing"], "6.4 0.7 9.7": ["hangings"], "10.9 17.6 8.6": ["smirking"], "4.3 15.5 9.7": ["obtuse"], "-1.1 5.9 3.6": ["solemnity"], "14.6 4.3 3.5": ["purring"], "18.3 -1.6 2.8": ["fledging"], "13.3 1.1 0.7": ["kitted"], "0.7 5.6 12.3": ["grumbles"], "11.0 13.6 8.3": ["pissing"], "12.7 10.6 8.5": ["backboards"], "-1.2 6.9 9.2": ["lt"], "15.3 12.4 19.0": ["twig"], "2.8 8.4 16.2": ["necktie"], "11.2 5.9 -0.8": ["hoodwinked"], "4.8 10.3 0.8": ["beautifying"], "6.4 11.3 6.7": ["winked"], "-8.1 2.4 4.1": ["reminisces"], "14.3 1.5 3.5": ["damped"], "2.7 20.5 17.3": ["hath"], "7.2 11.3 5.0": ["torchbearer"], "14.7 6.7 14.7": ["fistful"], "9.8 9.8 12.5": ["outsourcers"], "-2.0 -3.0 1.7": ["logon"], "11.1 -0.9 4.3": ["concessionaires"], "14.1 7.0 17.6": ["puppeteer"], "-4.3 4.1 1.2": ["remarketing"], "4.0 2.4 9.1": ["verging"], "-2.4 9.5 4.7": ["analgesic"], "-1.7 11.7 10.6": ["wisecracks"], "4.5 22.6 10.1": ["goad"], "9.8 4.8 13.0": ["shears"], "6.8 8.7 8.0": ["limps"], "3.1 30.7 14.2": ["kamikaze"], "8.7 10.3 38.9": ["orca"], "18.5 11.2 25.9": ["sloth"], "4.4 7.0 9.3": ["riffing"], "7.1 13.9 13.8": ["shins"], "6.8 29.4 4.6": ["wingman"], "3.0 0.1 12.0": ["moldings"], "11.7 6.4 3.9": ["electrics"], "2.6 5.2 8.6": ["pyrite"], "8.0 13.1 23.2": ["oars"], "4.0 12.3 10.7": ["dryly"], "5.3 -5.3 10.2": ["mockumentary"], "15.3 4.2 8.0": ["quickening"], "0.8 11.6 7.7": ["ardor"], "-10.9 -1.1 -7.4": ["deputation"], "11.7 5.5 2.6": ["caffeinated"], "3.4 16.5 -2.1": ["scurrilous"], "11.8 1.5 8.1": ["wholesaling"], "14.1 11.4 11.2": ["playmate"], "0.9 7.6 7.7": ["concussed"], "-8.5 5.3 5.1": ["rebook"], "0.2 12.5 -2.7": ["christian"], "-1.3 11.3 5.5": ["inattentive"], "13.3 7.4 1.5": ["shivers"], "14.1 11.6 -0.1": ["sleuth"], "7.2 10.6 26.3": ["hatchlings"], "-2.5 4.2 10.8": ["defrocked"], "11.6 11.1 0.5": ["conman"], "3.5 0.6 34.8": ["scallions"], "6.1 5.1 0.9": ["overexposure"], "14.3 14.9 14.3": ["weirdo"], "7.6 5.5 20.6": ["slough"], "7.1 14.5 9.7": ["dismissively"], "3.1 9.8 7.0": ["machined"], "9.4 19.5 7.4": ["perverts"], "-2.9 6.1 15.9": ["grout"], "17.4 -1.1 15.0": ["overstuffed"], "0.9 4.1 -0.3": ["permeability"], "11.4 17.6 9.9": ["crony"], "11.5 -2.5 12.0": ["su"], "-0.4 2.2 -1.5": ["meditations"], "5.5 -1.1 13.9": ["noncompetitive"], "2.6 8.3 12.8": ["moneyed"], "3.9 1.8 5.7": ["gymnastic"], "-3.9 10.1 3.7": ["exaggerations"], "-6.9 5.6 7.3": ["downpayment"], "1.8 8.5 17.8": ["magnetite"], "-4.4 9.6 7.4": ["infanticide"], "2.3 7.2 8.8": ["archeologist"], "5.4 -6.7 5.8": ["calender"], "-2.6 -4.8 3.6": ["biomaterials"], "2.9 18.0 7.8": ["asymmetry"], "6.4 4.4 6.6": ["chested"], "7.0 0.6 -2.4": ["scaleable"], "-3.3 2.8 6.5": ["elementaries"], "9.8 9.1 2.2": ["scaremongering"], "7.3 -7.7 17.7": ["bibs"], "-7.5 13.6 6.8": ["generalities"], "-0.5 1.0 4.0": ["flutist"], "7.4 7.5 10.1": ["quarantines"], "8.5 4.1 2.8": ["cuddled"], "1.5 4.8 5.5": ["whitepaper"], "-3.7 0.5 1.8": ["roomed"], "10.7 4.0 6.0": ["friday"], "17.4 0.3 4.9": ["sweetening"], "5.2 2.2 13.3": ["bodice"], "3.8 15.6 4.5": ["numbed"], "-4.9 0.1 0.7": ["letterwinner"], "4.5 16.6 7.9": ["outbuilding"], "4.9 11.6 1.3": ["regenerated"], "3.5 16.9 6.1": ["excruciatingly"], "4.3 -2.0 -2.5": ["extenders"], "9.3 3.0 12.9": ["combs"], "-5.0 -0.3 10.8": ["pawned"], "2.0 4.0 7.9": ["crooned"], "14.4 12.1 34.4": ["fern"], "17.2 13.0 20.2": ["wiggling"], "18.7 1.9 25.9": ["toothpick"], "-9.3 -2.0 10.2": ["grafts"], "9.7 14.6 6.1": ["magnifies"], "-11.8 5.5 6.7": ["remortgage"], "17.0 9.3 4.8": ["lamppost"], "5.4 10.0 0.1": ["odorless"], "10.1 11.8 10.3": ["laughably"], "-5.5 6.6 1.0": ["translational"], "1.4 24.1 7.4": ["inflicts"], "11.8 6.4 10.5": ["askew"], "0.5 14.7 10.6": ["canons"], "9.1 7.6 9.7": ["thwarts"], "1.3 6.6 17.8": ["parka"], "-11.4 9.6 2.7": ["homeschool"], "6.2 20.0 9.5": ["antagonizing"], "11.1 10.7 9.4": ["linesmen"], "7.3 9.1 10.2": ["redirects"], "10.2 12.0 8.1": ["bamboozled"], "14.2 3.2 11.1": ["elaborately"], "8.3 6.1 4.7": ["shivered"], "-0.9 10.8 2.9": ["newsgathering"], "4.9 20.4 3.4": ["outmatched"], "8.2 8.8 4.8": ["titleholder"], "0.8 30.9 4.1": ["oppositions"], "-2.3 12.5 -0.3": ["inconsolable"], "-5.4 6.6 3.6": ["unpaved", "munsif"], "-9.2 8.6 2.9": ["articulates"], "17.7 20.8 3.2": ["spooks"], "14.5 3.9 12.4": ["leggy"], "-4.1 6.4 5.0": ["unmanaged"], "7.6 6.3 7.7": ["crossword"], "13.0 -1.3 10.5": ["canada"], "12.7 10.1 56.7": ["mussel"], "1.8 17.3 1.3": ["cockpits"], "1.6 3.2 1.8": ["voyeuristic"], "11.5 11.3 2.0": ["trickiest"], "4.1 16.9 -1.5": ["thirdly"], "6.4 15.2 2.7": ["embeds"], "15.3 6.6 8.0": ["french"], "12.2 21.7 7.1": ["riddles"], "1.9 4.8 5.9": ["griped"], "8.8 28.0 10.0": ["minefields"], "4.0 4.2 9.6": ["tomes"], "10.7 2.0 8.6": ["ab"], "7.8 13.1 3.2": ["marshaled"], "-10.0 8.5 -0.4": ["hypoglycemia"], "8.6 4.6 10.1": ["hyperlink"], "-2.9 11.0 6.6": ["watchword"], "12.3 8.9 6.4": ["undertaker"], "1.4 12.0 17.7": ["hoarders"], "0.2 4.1 7.9": ["interludes"], "17.9 7.2 3.1": ["proto"], "-4.7 6.2 4.9": ["probables"], "1.4 11.5 -0.6": ["ahold"], "1.5 15.3 4.6": ["cults"], "10.2 6.9 4.2": ["stokes"], "3.2 1.5 10.9": ["anthropological"], "9.2 4.0 2.3": ["picketers"], "3.3 16.0 5.9": ["unionism"], "5.4 6.5 12.3": ["trapeze"], "5.2 12.0 -1.5": ["counterclaims"], "0.7 1.1 44.9": ["sashimi"], "3.0 11.9 12.1": ["hibernate"], "-9.0 13.9 1.0": ["unselfishness"], "5.9 7.5 5.2": ["lain"], "6.9 4.6 13.7": ["mucking"], "-1.5 3.3 10.3": ["birthrate"], "-2.0 7.2 14.1": ["costuming"], "4.9 14.8 5.0": ["abstractions"], "-7.2 6.3 4.3": ["palliative"], "11.6 -4.2 10.5": ["swooned"], "-2.8 15.7 10.4": ["destitution"], "11.0 12.7 -0.6": ["assailing"], "7.1 2.3 24.6": ["kimono"], "3.3 -1.8 3.5": ["leva"], "-5.0 3.8 1.8": ["abridged"], "11.1 12.5 11.1": ["amusingly"], "10.0 3.7 18.6": ["spool"], "4.1 2.5 7.3": ["receptacles"], "11.2 4.3 -2.4": ["plumbed"], "20.1 9.3 14.1": ["smokestack"], "9.0 15.9 11.7": ["lunges"], "7.7 7.3 5.4": ["thicknesses"], "10.4 10.5 0.3": ["stewardess"], "-3.7 12.0 -0.6": ["diminution"], "-1.5 8.8 30.9": ["chilies"], "2.9 11.7 8.4": ["anthemic"], "2.7 13.1 13.2": ["ironman"], "7.8 11.1 0.9": ["trodden"], "8.0 12.9 9.8": ["absurdities"], "12.4 8.8 37.9": ["walrus"], "-6.6 6.5 5.8": ["freelancing"], "8.7 9.4 19.1": ["croquet"], "-0.5 11.8 5.2": ["diverging"], "2.2 19.6 8.4": ["soulmate"], "3.0 2.6 7.4": ["cortex"], "-5.2 0.8 -2.0": ["electrolyte"], "10.0 9.9 3.4": ["huddles"], "5.9 14.9 3.6": ["ardently"], "-0.6 1.4 4.2": ["endocrinology"], "-3.1 5.7 2.6": ["thematically"], "-3.6 -2.6 1.9": ["sealants"], "8.7 7.5 13.3": ["hurdling"], "8.2 8.6 13.4": ["wisecracking"], "11.8 19.4 13.8": ["fated"], "-0.1 15.4 8.8": ["discouragement"], "7.0 -0.7 4.4": ["incubated"], "1.0 6.8 4.8": ["timepiece"], "-1.5 3.0 6.5": ["distilling"], "-5.0 1.5 2.7": ["overruling"], "8.7 7.8 23.4": ["munchies"], "-2.1 5.5 1.9": ["sidetrack"], "10.3 6.2 13.0": ["piazza"], "3.3 2.4 -3.8": ["mischaracterized"], "-2.5 11.0 18.0": ["liqueur"], "26.1 11.6 16.9": ["friggin"], "1.6 4.3 9.5": ["dan"], "6.8 21.4 5.6": ["proletariat"], "10.7 6.7 3.2": ["urinals"], "-1.1 0.8 7.1": ["leathers"], "5.2 2.3 16.6": ["finery"], "2.8 2.7 22.1": ["alpaca"], "4.3 12.9 8.3": ["forgetfulness"], "2.7 6.9 0.6": ["maximal"], "3.2 -1.8 2.4": ["graf"], "9.2 7.5 10.3": ["smudge"], "-1.6 13.1 2.9": ["cantonment"], "22.8 3.8 4.1": ["collapsible"], "0.9 6.7 1.4": ["chiding"], "-2.8 4.2 9.0": ["equivalency"], "0.8 3.6 46.3": ["chowder"], "7.2 8.7 26.4": ["shanty"], "6.4 8.2 13.2": ["unadorned"], "2.6 32.2 8.6": ["wickedness"], "-6.1 11.4 3.8": ["stylistically"], "-2.4 -1.4 -1.0": ["chauffeured"], "9.6 13.0 4.2": ["powerbrokers"], "2.9 12.3 15.1": ["gland"], "9.0 15.9 6.1": ["thousandth"], "8.9 8.8 0.4": ["letterbox"], "-7.5 8.9 0.6": ["gelling"], "0.1 8.1 0.3": ["parleys"], "2.7 9.6 5.3": ["freshened"], "5.0 14.1 9.7": ["mutter"], "7.6 16.3 5.7": ["determinedly"], "2.8 3.4 -0.4": ["hysterics"], "-4.9 -0.2 3.9": ["telehealth"], "0.2 15.1 16.8": ["commoner"], "-2.3 14.7 -3.9": ["marginalizing"], "1.7 4.4 6.4": ["irreverence"], "-0.3 11.3 10.9": ["aussie"], "-0.4 11.3 6.8": ["masturbate"], "5.9 4.1 -2.1": ["interconnections"], "2.2 7.9 -1.5": ["arousing"], "15.7 4.5 2.8": ["sweatshops"], "5.2 7.5 1.8": ["ruggedized"], "6.2 3.9 16.4": ["lowlands"], "13.9 2.9 8.7": ["frumpy"], "0.5 11.1 4.6": ["inasmuch"], "0.2 9.6 28.0": ["snorkel"], "3.2 9.6 6.1": ["snorted"], "-2.0 -0.4 7.5": ["biked"], "8.3 0.9 9.5": ["sectioned"], "8.8 10.5 6.0": ["stow"], "4.8 7.3 18.8": ["admirals"], "3.7 12.4 2.4": ["celebrant"], "-1.5 12.3 3.5": ["victimizing"], "-5.9 3.2 23.3": ["cumin"], "1.4 10.0 6.1": ["mortgaging"], "21.0 -5.7 1.3": ["sevenfold"], "14.3 8.0 12.4": ["magenta"], "1.4 7.0 16.8": ["tramadol"], "10.5 -2.7 14.4": ["mummified"], "3.3 -2.0 -3.0": ["reprocessed"], "15.7 10.5 3.9": ["spews"], "0.1 9.0 1.5": ["curt"], "6.2 9.9 7.0": ["nonstarter"], "3.4 2.3 11.8": ["rinsed"], "7.7 23.2 0.5": ["perceiving"], "4.3 18.1 -3.2": ["crossroad"], "26.7 21.1 23.2": ["cobra"], "1.4 3.1 -0.6": ["manhandling"], "7.0 1.6 7.5": ["jubilee"], "1.4 5.9 7.3": ["cloying"], "7.3 25.5 4.7": ["reflexive"], "-5.4 5.8 1.7": ["powertrains"], "-2.8 26.4 -0.9": ["survivable"], "17.3 13.6 0.6": ["menaced"], "2.9 15.4 7.6": ["shrewdly"], "-3.9 8.9 11.1": ["homesteads"], "-8.1 9.6 2.0": ["cusecs"], "-11.1 12.3 2.5": ["unsaid"], "10.8 10.6 8.4": ["nooses"], "3.4 9.4 15.1": ["arborist"], "-1.9 9.9 5.7": ["revolvers"], "3.2 0.9 3.8": ["dabbed"], "0.2 13.5 6.0": ["comity"], "2.0 15.8 6.7": ["boorish"], "13.7 3.2 -1.2": ["hypermarket"], "-0.1 8.4 13.4": ["sandal"], "-1.5 9.6 3.8": ["romanticized"], "-0.9 1.2 2.9": ["criterium"], "-3.0 -1.1 9.3": ["scoliosis"], "7.6 4.6 9.8": ["swingers"], "1.9 2.0 12.3": ["chafing"], "0.3 7.0 9.0": ["hardback"], "23.6 14.0 17.7": ["upturned"], "12.3 7.9 -1.2": ["overcharge"], "4.9 10.6 9.3": ["grudging"], "7.1 10.4 8.3": ["squatter"], "1.0 3.6 17.1": ["pavers"], "-1.4 9.3 4.4": ["frictions"], "4.3 11.2 -0.5": ["unexploded"], "13.2 2.7 6.3": ["gran"], "3.7 15.6 9.3": ["exponents"], "9.7 2.5 12.6": ["statuettes"], "13.9 12.3 11.8": ["girding"], "1.8 29.9 13.0": ["sandstorms"], "13.5 -2.3 6.8": ["twentysomethings"], "3.8 16.9 3.7": ["unobstructed"], "-0.5 22.3 6.2": ["utters"], "18.1 8.2 8.4": ["petro"], "4.8 2.3 19.4": ["pinky"], "-4.1 1.3 6.2": ["nullification"], "8.4 12.1 5.3": ["collectable"], "-4.6 9.9 0.2": ["rejoinder"], "4.6 7.6 13.9": ["vertebrates"], "13.9 11.0 2.0": ["sniffs"], "12.3 14.1 19.1": ["submersible"], "0.3 -4.5 1.8": ["bcm"], "11.3 8.8 6.9": ["twitchy"], "6.4 12.7 2.8": ["humanize"], "15.6 17.8 13.4": ["immovable"], "3.5 15.0 4.8": ["litigant"], "-1.7 -0.2 2.1": ["yd"], "11.9 30.3 10.2": ["rogues"], "12.7 16.0 20.0": ["breadbasket"], "2.0 5.9 -7.1": ["litigations"], "18.4 18.9 11.0": ["burrowing"], "5.8 32.4 5.2": ["counterattacks"], "14.9 8.0 4.9": ["flings"], "5.4 6.2 12.4": ["intercollegiate"], "0.5 8.2 8.9": ["spank"], "-0.1 10.3 11.4": ["walkabout"], "6.7 4.8 23.5": ["kebabs"], "1.5 29.0 -3.3": ["nonbelievers"], "3.1 -1.2 10.8": ["soo"], "5.2 7.9 6.7": ["incredulity"], "12.2 4.2 17.6": ["fuchsia"], "0.5 8.6 1.1": ["energizes"], "17.3 32.2 15.1": ["turrets"], "6.0 -7.7 -1.6": ["pix"], "4.8 -0.8 15.8": ["baubles"], "10.9 8.1 2.5": ["deriding"], "-7.7 0.1 -4.1": ["undersigned"], "17.2 1.3 11.8": ["roil"], "13.9 10.7 5.2": ["stupor"], "0.7 20.9 3.8": ["uncivilized"], "8.4 25.2 20.3": ["mosquitos"], "2.4 12.0 14.7": ["smooch"], "1.5 10.9 1.8": ["sinuses"], "19.5 10.0 12.2": ["peculiarly"], "9.5 6.6 10.5": ["scruff"], "-6.2 2.3 -5.2": ["misbehaved"], "4.1 10.0 -1.0": ["exhaled"], "0.2 8.1 15.5": ["vegans"], "-5.9 1.2 5.8": ["lettings"], "-5.0 10.7 6.9": ["subjectivity"], "2.9 4.3 1.2": ["scours"], "6.9 9.4 1.2": ["aftereffects"], "15.5 -0.4 13.6": ["sloshing"], "4.6 14.2 6.1": ["skilfully"], "2.2 -2.2 5.7": ["unfreeze"], "12.1 3.5 11.3": ["attractively"], "9.4 9.8 16.4": ["exportation"], "13.7 8.5 -0.4": ["presences"], "0.8 6.1 11.5": ["rostrum"], "-10.3 -0.6 -3.2": ["rabbinical"], "-4.7 1.5 5.6": ["violinists"], "3.4 10.3 11.4": ["laconic"], "-0.9 2.4 15.2": ["whey"], "14.6 -5.9 8.2": ["creche"], "0.1 6.6 11.4": ["cheekbones"], "18.0 7.0 36.7": ["pelican"], "16.8 8.2 17.1": ["daisies"], "10.4 3.1 36.2": ["cantaloupe"], "4.8 4.8 3.5": ["coefficient"], "8.0 6.1 35.5": ["dill"], "1.0 14.6 11.5": ["humorless"], "8.2 12.7 7.0": ["hoodoo"], "5.4 1.8 0.7": ["dampener"], "-3.7 11.4 0.9": ["demote"], "1.5 6.0 6.3": ["shortchanging"], "7.7 5.1 1.5": ["outlasts"], "6.0 16.0 11.7": ["fisted"], "-0.7 0.2 9.8": ["placers"], "10.4 18.8 12.4": ["rednecks"], "9.8 2.3 14.1": ["botching"], "9.7 8.8 2.3": ["sacrilegious"], "6.5 -1.1 -3.6": ["redesigns"], "7.3 10.6 4.9": ["overexposed"], "-7.1 12.7 9.6": ["underreporting"], "0.3 -1.7 1.0": ["hashing"], "-0.9 10.7 34.0": ["horseradish"], "11.9 10.3 9.6": ["veep"], "3.9 -1.8 5.2": ["polytechnic"], "2.1 9.8 7.8": ["subtler"], "13.7 -0.2 7.2": ["mth"], "-6.5 3.6 6.9": ["encores"], "20.7 4.7 12.4": ["poof"], "17.5 17.1 18.5": ["awesomeness"], "1.1 7.2 7.0": ["breakups"], "-2.1 9.6 8.0": ["gameday"], "3.8 20.1 7.4": ["archetypes"], "7.1 13.4 13.8": ["laughingly"], "-6.9 0.4 1.8": ["anesthesiologists"], "-2.7 8.7 -1.4": ["decertification"], "-0.6 12.2 7.2": ["tamely"], "12.4 6.5 0.5": ["astrophysicist"], "13.4 10.9 8.8": ["nudges"], "-2.7 -2.8 12.5": ["backlogged"], "-3.3 5.3 1.0": ["affirmations"], "-4.0 9.8 2.1": ["admonish"], "0.9 12.0 -1.3": ["insinuate"], "5.9 14.2 20.5": ["marshlands"], "18.9 8.7 7.6": ["populating"], "15.1 10.0 17.6": ["hovercraft"], "-6.7 16.7 0.8": ["admonishment"], "7.0 5.1 8.1": ["acoustical"], "-8.7 20.1 6.1": ["factionalism"], "10.5 8.0 4.8": ["predominance"], "13.4 11.4 5.5": ["corkscrew"], "5.5 8.0 14.0": ["ooh"], "6.4 1.0 14.3": ["whiter"], "9.8 11.5 4.4": ["identically"], "13.2 8.4 8.3": ["dorky"], "2.3 0.7 13.9": ["undergrads"], "2.6 6.9 4.5": ["wholehearted"], "5.1 11.5 1.7": ["coddling"], "4.1 2.0 9.3": ["caroling"], "11.4 -0.3 1.2": ["suffix"], "3.4 12.8 11.8": ["pretexting"], "17.9 11.1 12.9": ["magnificence"], "12.6 1.4 2.4": ["teeters"], "9.0 32.6 9.1": ["tormentor"], "5.1 1.5 6.6": ["nonvoting"], "2.9 10.8 16.4": ["capsize"], "5.2 11.6 6.1": ["grasps"], "3.9 -0.9 18.8": ["trestle"], "-5.7 5.6 0.8": ["creditworthy"], "9.1 9.0 8.9": ["flask"], "-7.7 18.6 -4.3": ["misinterpret"], "12.3 3.0 21.8": ["tangerine"], "-9.1 13.4 4.5": ["readjustment"], "8.7 6.0 5.7": ["vestibule"], "10.7 4.8 4.4": ["tills"], "-1.9 17.2 5.1": ["reproach"], "5.1 14.9 0.6": ["stairways"], "2.1 5.3 35.9": ["radishes"], "-8.3 -1.1 1.7": ["neurologic"], "5.5 4.3 6.5": ["eking"], "16.9 13.8 12.9": ["smackdown"], "17.9 24.5 2.5": ["blitzkrieg"], "-0.1 4.3 5.3": ["emulator"], "-2.4 10.0 6.2": ["shareowners"], "-6.3 -3.2 11.7": ["menstruation"], "17.7 9.9 6.1": ["envelop"], "5.4 -2.2 8.0": ["splurging"], "-0.7 20.8 7.3": ["supposition"], "8.2 21.6 6.3": ["manipulator"], "-3.3 3.8 8.5": ["putbacks"], "-8.0 13.8 8.1": ["incarcerate"], "3.6 30.7 11.3": ["expeditionary"], "5.4 0.8 1.9": ["biochemist"], "-0.3 5.8 10.4": ["overstaying"], "-1.2 18.2 1.1": ["mistreat"], "-0.9 17.5 19.5": ["starboard"], "9.0 5.2 11.5": ["whoa"], "8.2 3.6 20.8": ["floaters"], "6.9 14.3 7.0": ["chi"], "8.5 11.0 7.5": ["dividers"], "8.0 6.2 5.4": ["inauspicious"], "-0.6 6.7 5.6": ["showtimes"], "7.0 6.4 31.9": ["pineapples"], "2.9 10.0 23.3": ["motorboat"], "-5.5 10.3 3.6": ["stimulative"], "6.6 1.0 10.7": ["patterning"], "13.8 2.0 11.3": ["hijinks"], "3.8 8.9 8.2": ["prolongs"], "-7.0 1.9 4.2": ["agronomist"], "20.4 2.3 10.4": ["clanging"], "-2.7 -2.0 3.4": ["podiatrist"], "-1.0 10.2 27.6": ["potting"], "-7.4 13.7 4.4": ["decedent"], "-4.7 10.4 3.1": ["benediction"], "-2.4 6.2 2.2": ["babysit"], "11.5 6.0 12.1": ["punctuating", "thumpy"], "-7.8 4.1 -1.2": ["expounded"], "8.4 22.7 12.6": ["unchanging"], "1.7 3.6 7.1": ["coffeehouses"], "9.3 15.4 7.0": ["haka"], "5.1 12.5 15.1": ["entomology"], "-0.5 13.0 20.1": ["tiller"], "9.3 -0.2 5.6": ["grooved"], "3.0 7.1 5.0": ["meting"], "7.4 22.4 7.7": ["timidity"], "6.4 11.7 16.0": ["picnicking", "sandlot"], "0.7 1.1 5.4": ["retailed"], "1.5 12.2 -1.5": ["ordeals"], "-4.3 5.7 8.1": ["turboprop"], "18.9 8.0 9.5": ["unfurling"], "21.6 6.1 14.9": ["honeycomb"], "4.2 14.6 -3.2": ["skinheads"], "-2.4 13.8 6.1": ["backbencher"], "9.5 10.0 5.0": ["trespassed"], "4.9 3.3 4.4": ["latches"], "14.1 13.4 15.2": ["shaman"], "-3.3 6.2 10.3": ["rinsing"], "1.9 6.0 14.7": ["cymbals", "vity"], "19.1 6.2 19.5": ["vats"], "-3.4 9.7 24.8": ["potters"], "3.9 7.5 2.5": ["optometrists"], "-3.2 2.9 23.5": ["wetsuit"], "0.7 11.0 6.6": ["goalwards"], "6.6 12.2 6.6": ["bondholder"], "11.1 9.0 15.6": ["flabby"], "-0.1 0.9 22.9": ["saute"], "8.4 12.2 8.6": ["underachievers"], "9.4 18.8 14.7": ["rattlesnakes"], "16.8 5.1 16.2": ["tarpaulins"], "-3.1 8.9 4.7": ["discerned"], "-14.9 6.6 4.0": ["reoffending"], "-1.9 2.7 16.3": ["craftspeople"], "-7.6 4.3 4.5": ["multicast"], "3.9 6.7 8.5": ["zippers", "javascript"], "12.5 11.2 3.8": ["oscillating"], "1.0 5.6 4.3": ["garbled"], "-9.4 9.6 5.6": ["acuity"], "4.6 11.8 1.4": ["dishonestly"], "9.6 13.0 5.6": ["surreptitious"], "10.0 19.3 9.0": ["sentinel"], "10.8 9.8 13.6": ["chins"], "8.7 -2.5 -2.5": ["directorships"], "13.1 22.2 28.1": ["sparrow"], "11.7 5.2 14.1": ["regs"], "0.3 4.5 9.7": ["pancreatic"], "1.9 5.3 6.1": ["pacifier"], "12.0 0.2 27.7": ["slivers"], "4.3 3.6 11.6": ["androgynous"], "20.9 25.5 4.2": ["menacingly"], "15.3 7.2 -4.5": ["rebuffing"], "-1.4 0.8 17.2": ["sideburns"], "3.2 2.5 11.3": ["decorators", "nonperishables"], "-2.8 13.4 3.9": ["monogamy"], "-2.1 5.5 10.1": ["asynchronous"], "3.4 3.8 26.3": ["pelts"], "13.1 16.8 18.5": ["pecking"], "7.6 -1.6 18.4": ["wan"], "10.4 3.1 13.5": ["milkshakes"], "-2.3 4.8 7.6": ["criminologist"], "8.4 5.0 5.0": ["foisted"], "17.1 5.5 10.0": ["accoutrements"], "-6.7 5.2 8.8": ["priestly"], "12.5 7.7 -0.8": ["subsumed"], "6.1 14.0 21.3": ["skiffs"], "-4.8 5.7 59.0": ["watermen"], "1.1 11.2 8.4": ["perpetuation"], "-11.9 6.9 -1.0": ["prophylaxis"], "-4.2 15.7 6.0": ["exhortation"], "0.2 4.9 5.0": ["bu"], "9.8 4.5 4.3": ["generically"], "10.7 11.2 15.5": ["rudderless"], "3.2 16.9 -1.0": ["untruths"], "-0.4 16.0 9.6": ["expressionless"], "12.1 10.4 35.4": ["turnips"], "3.5 13.7 8.6": ["bellow"], "9.6 6.0 2.0": ["monikers"], "-0.6 -1.3 -5.0": ["counterproposal"], "-8.3 13.9 5.5": ["prudential"], "7.1 7.7 7.9": ["epileptic"], "4.4 13.0 -6.4": ["stigmatize"], "2.4 9.8 16.2": ["browning"], "5.1 6.6 1.1": ["exertions"], "16.8 12.2 9.3": ["backsides"], "8.7 -0.1 12.2": ["paleontologists"], "2.6 13.0 13.0": ["gerrymandering"], "13.9 9.5 7.2": ["cradles"], "-13.3 11.6 14.2": ["fungicides"], "8.1 13.2 8.5": ["pacemen"], "10.0 20.4 11.7": ["growls"], "5.9 2.0 4.5": ["discos"], "-0.2 1.9 8.1": ["compositional"], "9.7 9.8 7.4": ["deconstruct"], "4.9 17.9 5.8": ["thuggish"], "3.6 9.4 7.6": ["dormancy"], "12.1 11.2 6.8": ["baying"], "2.9 17.8 4.9": ["fallible"], "9.5 7.7 10.9": ["meatpacking"], "8.6 9.4 2.0": ["unblocked"], "8.6 4.2 6.0": ["nips"], "4.1 14.1 11.1": ["knuckleballer"], "4.4 20.3 8.8": ["desolation"], "2.7 9.1 12.5": ["ribbed"], "-4.5 2.4 -0.9": ["timepieces"], "1.1 5.8 3.0": ["quantification"], "4.1 13.7 2.3": ["inoculate"], "-3.6 12.3 6.3": ["recites"], "26.2 7.5 6.1": ["noisily"], "-2.1 -1.4 5.5": ["microcredit"], "6.5 1.6 34.5": ["feta"], "3.7 -1.8 6.8": ["tendonitis"], "1.0 4.5 9.2": ["mbps"], "5.2 28.7 14.8": ["unknowable"], "12.9 8.4 10.9": ["slackers"], "11.3 11.0 14.8": ["predawn"], "0.7 13.7 15.3": ["wipers"], "8.5 16.7 12.5": ["elitists"], "-6.2 6.7 -4.5": ["sms"], "-3.6 23.4 8.4": ["retorts"], "13.5 20.1 4.3": ["tribesman"], "10.7 16.5 11.2": ["upmanship"], "-5.9 34.0 4.5": ["isolationist"], "12.1 10.1 12.4": ["cams"], "7.1 11.8 9.3": ["telemarketer"], "8.6 15.6 3.4": ["sharpens"], "23.8 28.2 16.7": ["ninjas"], "1.4 1.6 27.3": ["paprika"], "1.8 4.1 5.3": ["retread"], "-1.1 6.1 3.5": ["nonpolitical"], "1.7 9.2 9.4": ["reproduces"], "18.8 16.6 23.8": ["carnivorous"], "6.5 11.0 3.9": ["insignificance"], "5.9 14.3 6.6": ["rapturous"], "-2.4 40.3 0.1": ["apostate"], "15.5 13.2 12.5": ["frowning"], "16.2 6.5 2.2": ["dalliance"], "12.0 1.3 4.7": ["apace"], "5.1 8.4 15.3": ["sill"], "5.3 -3.8 -1.5": ["beautician"], "-2.4 12.6 5.5": ["dissonance"], "-3.4 5.1 8.0": ["marathoner"], "6.5 9.0 11.6": ["carom"], "7.3 11.7 10.9": ["monochromatic"], "10.2 5.2 3.3": ["transcontinental"], "8.0 9.6 5.9": ["rhythmically"], "13.4 8.0 2.9": ["liquefaction"], "8.2 8.6 14.0": ["stencil"], "5.6 24.7 9.4": ["sociopath"], "11.3 4.5 8.0": ["gangrene"], "-8.9 13.8 -1.3": ["paraphrased"], "-1.3 25.3 11.7": ["mutineers"], "2.1 -0.8 28.6": ["char"], "0.9 11.4 9.9": ["inordinately"], "18.3 14.6 6.7": ["joyously"], "-0.2 18.6 12.8": ["dysentery"], "12.5 5.2 18.6": ["bratwurst"], "9.1 6.2 6.5": ["backlighting"], "11.8 10.9 12.9": ["lookin"], "3.8 -5.7 2.7": ["md"], "6.4 1.2 18.9": ["corks"], "7.9 6.1 13.9": ["emulsion"], "7.7 8.0 9.6": ["straitjacket"], "6.8 10.7 12.4": ["retrieves"], "-0.0 5.0 18.5": ["trotters"], "1.4 5.1 5.9": ["reconstitution"], "13.4 11.2 17.2": ["viscous"], "3.9 15.1 4.7": ["despatch"], "2.6 6.3 6.8": ["hobbyist"], "3.8 11.0 5.0": ["sanctimonious"], "-2.9 7.9 9.2": ["mustangs"], "4.8 6.2 4.4": ["sleuthing"], "10.9 5.9 7.4": ["lifer"], "9.6 2.3 14.0": ["deconstructed"], "1.6 10.1 6.5": ["neuroblastoma"], "6.9 18.2 4.1": ["inferiority"], "-0.8 -0.3 6.8": ["unallocated"], "6.3 4.9 3.9": ["bmi"], "0.9 16.4 16.6": ["overhand"], "15.3 11.8 6.0": ["bellows"], "-0.5 3.0 -2.0": ["nagged"], "-7.6 8.0 8.3": ["rangeland"], "-3.0 10.7 4.8": ["lignite"], "-2.8 8.5 11.8": ["piste"], "-3.3 11.2 13.6": ["tossup"], "6.8 6.3 9.3": ["swansong"], "3.2 7.9 6.5": ["connectedness"], "10.2 8.3 4.2": ["stepdad"], "4.5 2.5 4.7": ["waylaid"], "-4.5 8.6 12.1": ["contango"], "8.4 22.7 5.2": ["imposter"], "7.5 11.0 0.5": ["meritless"], "6.9 3.8 13.9": ["nudes"], "9.3 3.1 1.1": ["dazzles"], "-1.3 6.8 7.3": ["telaprevir"], "11.3 2.6 21.2": ["songbird"], "20.3 8.2 8.5": ["peddler"], "2.6 4.5 6.5": ["encapsulation"], "15.5 13.2 13.5": ["wipeout"], "6.8 11.0 13.9": ["mistimed"], "16.5 4.2 1.6": ["goldmine"], "14.8 10.1 2.0": ["outwards"], "13.7 7.0 6.4": ["bedraggled"], "-0.8 9.3 5.2": ["unfamiliarity"], "2.5 3.1 -3.1": ["drubbed"], "11.1 -0.1 9.8": ["gratis"], "-0.4 1.6 9.0": ["attired"], "-0.7 11.5 8.1": ["pleasantries"], "4.3 2.0 25.4": ["ducklings"], "3.2 10.6 -1.2": ["synced"], "7.8 6.5 6.3": ["sloped"], "8.9 16.3 9.9": ["minaret"], "1.2 19.2 -0.3": ["gunfights"], "11.7 6.0 8.7": ["outfitter"], "1.1 15.9 -1.8": ["diatribes"], "6.5 12.2 9.1": ["comma"], "1.1 4.9 15.7": ["carbonate"], "-0.8 7.8 1.3": ["bogies"], "-0.5 0.7 4.8": ["compilers"], "-1.3 6.4 8.3": ["excepting"], "0.7 4.7 3.8": ["pg"], "8.1 4.6 17.1": ["tastier"], "17.4 19.7 8.9": ["unwary"], "5.9 9.4 4.6": ["zealously"], "-7.0 11.7 6.9": ["tasers"], "6.7 22.2 12.3": ["wrongheaded"], "-4.1 2.5 10.8": ["tabla"], "-6.0 4.3 2.3": ["remodels"], "3.6 13.8 33.0": ["phytoplankton"], "16.0 2.7 0.4": ["careered"], "-1.3 5.4 8.0": ["warranting"], "6.5 14.2 14.8": ["insulator"], "-0.9 4.9 0.5": ["incentivized"], "1.2 5.5 1.1": ["oxytocin"], "7.4 31.9 9.0": ["hegemonic"], "4.2 10.9 7.4": ["schema"], "-14.3 9.2 -4.9": ["corroboration"], "6.3 8.9 1.4": ["unfeasible"], "9.0 2.2 9.5": ["southside"], "16.7 4.9 3.1": ["retracting"], "17.4 16.6 10.4": ["pivoted"], "2.5 4.6 5.6": ["shortchange"], "9.0 12.0 35.6": ["gators"], "1.3 6.4 5.9": ["decompression"], "0.5 11.4 8.3": ["landholders"], "17.4 14.0 11.0": ["broomstick"], "-9.0 -2.1 8.0": ["airings"], "0.7 6.1 11.1": ["fabless"], "-3.5 9.3 -2.0": ["inducting"], "3.1 3.8 37.0": ["polenta"], "-7.4 4.8 9.0": ["committeeman"], "15.3 15.6 2.9": ["outmaneuvered"], "1.6 7.2 18.8": ["impoundment"], "-6.8 32.2 6.6": ["gallantry"], "1.0 6.9 5.4": ["reverent"], "5.2 12.1 3.5": ["perilously"], "11.9 8.5 -2.6": ["undiminished"], "16.5 11.5 6.8": ["stiffening"], "4.0 4.1 1.9": ["caned"], "21.1 -2.1 9.3": ["teacup"], "13.0 26.4 4.0": ["conquers"], "6.4 6.8 7.5": ["copping"], "-0.9 5.2 -3.3": ["conversant"], "1.4 26.9 8.0": ["devastatingly"], "6.2 0.2 4.4": ["yellowing"], "18.2 28.9 11.4": ["sentry"], "13.1 7.9 11.7": ["dopey"], "10.7 6.2 -3.0": ["peeks"], "-5.2 3.2 4.1": ["jotted"], "7.3 9.9 19.7": ["bedbug"], "2.8 7.1 -0.4": ["pacy"], "3.3 6.4 0.7": ["undistinguished"], "26.8 26.0 22.1": ["orb"], "-3.0 5.5 10.3": ["scrubbers"], "5.3 5.0 15.5": ["tulle"], "3.0 12.9 1.1": ["plausibly"], "0.6 -0.4 0.3": ["sportier"], "-3.7 8.2 9.9": ["hairline"], "10.1 11.8 1.2": ["provocatively"], "-4.8 8.8 8.1": ["crewed"], "7.8 19.5 19.4": ["suplex"], "0.2 4.2 10.2": ["sanded"], "-0.5 5.6 10.8": ["stratified"], "6.6 2.3 8.0": ["bickered"], "6.8 5.7 6.5": ["indigenes"], "13.7 15.2 -2.4": ["cozying"], "19.7 17.4 10.6": ["ghouls"], "-1.4 0.6 -1.4": ["pancreatitis"], "7.4 8.9 7.3": ["smut"], "4.5 25.7 11.5": ["despotism"], "9.3 7.3 9.8": ["princely"], "3.6 2.0 11.6": ["paternalistic"], "9.9 5.8 5.3": ["disposes"], "10.1 7.3 11.2": ["kindling"], "15.6 15.2 12.7": ["dork"], "-7.2 1.2 -1.7": ["courseware"], "6.7 14.7 6.1": ["fissure"], "3.5 -3.0 18.9": ["phosphates"], "5.1 4.1 -6.2": ["rebutting"], "-1.6 14.7 -0.1": ["declassify"], "2.6 5.8 21.5": ["snowshoe"], "8.0 4.4 6.3": ["absorbent"], "-1.8 13.6 9.9": ["epithets"], "16.9 7.8 3.1": ["christen"], "-7.2 2.6 5.4": ["anterior"], "4.3 6.9 24.5": ["pewter"], "6.1 1.9 -2.5": ["papered"], "7.5 24.4 9.5": ["sidekicks"], "-5.8 0.6 15.2": ["checkoff"], "10.9 15.0 8.1": ["coyly"], "6.3 1.2 11.3": ["talkin"], "16.4 19.7 7.6": ["mutating"], "10.6 20.5 3.8": ["homing"], "14.0 7.8 23.2": ["roadkill"], "4.3 15.2 3.1": ["homecourt"], "15.0 15.7 -3.9": ["democratizing"], "3.0 -1.1 1.9": ["nondenominational"], "3.9 14.3 5.0": ["corrode"], "2.1 3.3 -0.6": ["mouthwash"], "8.4 2.9 16.1": ["tablecloths"], "18.4 12.6 10.4": ["stomps"], "-0.6 9.8 3.9": ["usefully"], "9.4 12.1 4.3": ["screed"], "1.4 25.5 -2.7": ["indivisible"], "11.7 9.9 7.7": ["clattered"], "9.8 12.8 11.4": ["irreversibly"], "-4.9 7.7 1.2": ["demographically"], "6.3 6.6 8.4": ["blather"], "7.4 3.7 27.6": ["waterside"], "-3.7 -1.8 4.3": ["matric"], "2.0 2.1 2.6": ["tracheotomy"], "14.7 5.4 0.2": ["overhyped"], "5.5 4.8 17.0": ["jasmine"], "5.6 4.5 15.7": ["handrails"], "-1.5 7.0 1.2": ["tangent"], "12.9 17.4 25.2": ["termite"], "6.4 11.9 12.5": ["egging"], "10.4 17.8 32.5": ["loon"], "3.0 8.2 4.7": ["carol"], "6.9 9.1 5.5": ["sportsbook"], "3.5 -0.4 3.7": ["fussed"], "4.8 10.8 9.4": ["firetrucks"], "6.4 47.5 10.4": ["oppressor"], "13.6 5.8 25.0": ["tulip"], "-6.7 1.3 28.6": ["cardamom"], "-1.3 -9.0 0.3": ["regularize"], "5.2 9.8 34.3": ["patty"], "7.8 14.3 1.3": ["vandalize"], "-1.9 -1.1 0.5": ["homeopathic"], "1.8 12.0 0.7": ["infidelities"], "8.7 1.8 3.4": ["fume"], "12.3 10.0 1.8": ["signpost"], "-3.5 8.2 13.7": ["overeat"], "-0.1 12.5 -0.2": ["prophylactic"], "-6.8 5.3 6.5": ["contra"], "9.3 7.5 28.8": ["baguette"], "17.9 -2.5 7.9": ["flamed"], "-3.6 1.5 49.2": ["sockeye"], "7.3 11.4 0.2": ["profusely"], "10.4 8.0 11.0": ["smarmy"], "-13.5 8.7 22.0": ["varietals"], "10.4 -2.9 -2.7": ["latterly"], "3.5 7.9 3.7": ["admonishing"], "16.2 16.1 6.9": ["cataclysm"], "0.2 6.7 11.3": ["endoscopic"], "6.0 7.0 -1.8": ["blunting"], "2.1 11.0 4.2": ["understating", "interspace"], "-6.4 19.9 4.7": ["barrack"], "16.3 29.5 9.9": ["enslave"], "0.8 10.6 8.8": ["powerline"], "5.3 1.4 15.8": ["pantyhose"], "1.5 12.1 8.3": ["exhilarated"], "6.5 0.4 11.7": ["lilting"], "7.1 12.2 6.0": ["fluidly"], "7.2 12.9 6.9": ["fiefdoms"], "13.8 -0.7 7.1": ["spurted"], "9.6 8.0 11.0": ["lofting"], "-3.8 8.8 3.2": ["photojournalism"], "-0.1 7.5 4.7": ["danceable"], "5.5 6.3 2.1": ["workspaces"], "6.7 8.6 10.6": ["desi"], "10.7 15.9 8.4": ["reappears"], "9.9 13.0 3.5": ["repossess"], "-1.8 10.1 4.9": ["franchisors"], "21.6 19.4 6.0": ["catapults"], "15.3 8.6 0.8": ["reorganizes"], "8.6 6.6 0.7": ["bawling"], "5.9 19.9 7.2": ["lookouts"], "-1.2 8.5 4.8": ["downswing"], "-12.6 11.3 10.4": ["tillage"], "1.6 8.6 10.0": ["showboating"], "9.9 11.0 9.5": ["corralling"], "5.6 15.2 10.0": ["wickedly"], "19.6 12.2 4.4": ["shill"], "-1.9 8.6 4.8": ["cryptographic"], "5.6 8.7 27.0": ["pontoon"], "2.1 5.5 5.8": ["scrounge"], "-2.9 18.4 10.1": ["cockiness"], "13.3 13.2 43.6": ["starfish"], "-3.0 -1.8 -3.7": ["thrombosis"], "3.0 3.0 4.7": ["ps"], "12.9 8.1 3.9": ["farmhand"], "-4.0 9.9 5.6": ["capacitance"], "3.4 2.7 11.2": ["taillights"], "10.4 -0.2 15.8": ["mislabeled"], "1.6 2.4 8.7": ["foregone"], "2.6 4.4 8.6": ["ratepayer"], "12.5 25.6 2.4": ["omnipotent"], "3.7 3.7 -4.1": ["arbitrate"], "11.9 12.1 1.6": ["whisking"], "1.0 10.5 0.2": ["businessperson"], "15.3 3.9 2.8": ["curvaceous"], "-3.5 3.7 9.0": ["eventing"], "8.1 4.7 9.0": ["waterworks"], "19.4 18.4 10.9": ["mazes"], "19.9 15.7 8.9": ["stoically"], "8.2 9.5 1.8": ["ruptures"], "-3.5 4.7 2.1": ["upsides"], "-1.0 11.6 7.1": ["starches"], "5.8 3.4 11.5": ["splicing"], "13.2 28.2 3.1": ["stealthily"], "10.7 15.1 5.1": ["youre"], "0.2 -0.0 15.2": ["purebred"], "4.4 4.1 19.4": ["suds"], "12.4 8.5 7.2": ["weathers"], "8.7 27.4 12.9": ["coldly"], "20.0 10.2 5.8": ["flatulence"], "14.3 9.0 15.6": ["whacks"], "9.5 13.8 4.1": ["opacity"], "15.1 9.5 1.8": ["labyrinthine"], "13.9 7.7 26.0": ["tugboats"], "3.8 20.9 3.6": ["sycophants"], "6.6 7.1 3.7": ["armrest"], "13.3 -0.9 4.9": ["clanked"], "6.2 13.0 16.3": ["crapshoot"], "12.8 8.7 16.8": ["mandarins"], "5.3 1.4 6.2": ["jawbone", "flameproof"], "11.0 22.1 4.1": ["startle"], "0.5 6.1 8.1": ["transsexuals"], "1.2 7.0 11.1": ["subsets"], "5.1 4.8 9.3": ["savors"], "-8.7 16.9 6.7": ["motivators"], "1.6 6.8 15.8": ["san"], "6.6 8.6 4.7": ["hosing"], "2.1 10.6 7.3": ["westerly"], "-8.7 0.4 3.2": ["reconstructive"], "-8.3 0.2 15.5": ["tuitions"], "-1.8 7.2 3.4": ["cloistered"], "5.9 2.0 3.5": ["unclog"], "9.6 -0.8 4.8": ["rebid"], "11.0 -1.7 6.8": ["expos"], "-6.0 22.4 7.7": ["micromanaging"], "-3.2 9.1 7.2": ["neglectful"], "20.6 -7.5 2.2": ["sixfold"], "10.4 0.4 8.0": ["striptease"], "2.9 4.9 1.3": ["trialist"], "-5.2 3.6 7.5": ["chorale"], "22.8 12.4 9.1": ["oracle"], "1.7 9.3 3.5": ["mete"], "-3.6 22.4 4.6": ["sinned"], "4.8 -1.1 -0.4": ["faired"], "8.0 -1.0 7.8": ["paydays"], "-0.6 5.7 5.1": ["ypc"], "11.6 5.5 26.7": ["fondue"], "15.1 13.8 17.1": ["bruiser"], "13.9 10.2 9.9": ["tiptoe"], "-4.9 8.2 4.7": ["horsemanship"], "21.2 10.7 10.3": ["bionic"], "-1.8 7.6 9.2": ["welds"], "-5.3 1.8 2.7": ["trombonist"], "16.3 5.1 14.3": ["hobo"], "5.5 5.6 1.9": ["narcolepsy"], "4.9 7.8 7.3": ["fudged"], "10.0 -2.6 -0.2": ["assuaged"], "0.7 5.1 7.9": ["forfeitures"], "11.6 6.6 -1.6": ["pulsed"], "10.7 -9.5 -2.5": ["underwrote"], "4.1 -2.0 18.6": ["tweed"], "4.0 8.7 6.0": ["fudging"], "4.1 8.0 8.5": ["ribcage"], "2.6 12.6 6.8": ["academe"], "13.0 6.4 13.5": ["fairgoers"], "-3.9 6.5 -1.2": ["pedagogy"], "8.6 5.4 21.7": ["kebab"], "1.8 4.2 18.9": ["cornstarch"], "10.5 11.0 12.2": ["cad"], "16.4 11.7 7.9": ["drunkenly"], "12.5 9.3 10.2": ["begrudgingly"], "-2.0 -2.5 6.2": ["photocopied"], "5.8 0.8 12.9": ["thirtysomething"], "3.9 4.5 3.1": ["perceptible"], "0.1 14.9 9.4": ["semistate"], "0.1 -0.1 11.0": ["muni"], "-3.2 5.9 13.7": ["burros"], "11.7 7.4 18.0": ["creamed"], "4.5 8.8 9.6": ["xi"], "7.7 16.7 2.0": ["enrage"], "7.7 10.3 13.1": ["dooms"], "17.1 6.4 20.0": ["milky"], "-1.1 9.2 16.9": ["outboard"], "11.0 -2.5 15.6": ["caboose"], "2.7 23.7 4.8": ["instigators"], "4.5 13.3 25.3": ["drawbridge"], "4.9 6.0 2.7": ["asphyxiated"], "-2.8 6.5 14.0": ["reagent"], "1.8 -8.0 5.2": ["pedigrees"], "-1.2 5.3 14.6": ["perishables"], "-4.5 4.1 6.7": ["geriatrics"], "7.6 28.3 -1.1": ["propagandists"], "8.9 12.1 25.9": ["loons"], "0.0 6.9 26.2": ["powerboat"], "2.9 12.0 11.1": ["schtick"], "15.7 13.1 27.9": ["stingray"], "11.8 6.5 10.9": ["surrealist", "canoodle"], "0.7 -2.2 7.6": ["recommence"], "12.1 0.1 15.6": ["lacy"], "4.4 14.1 10.7": ["dismantlement"], "2.4 12.4 5.9": ["recalibrate"], "9.5 16.3 3.5": ["disables"], "1.2 8.6 -1.9": ["encrypting"], "-7.9 9.7 12.2": ["backfill"], "6.2 8.4 8.2": ["spouts"], "-3.5 12.9 5.5": ["tilling"], "10.6 -0.8 3.7": ["reinstalled"], "1.1 13.2 8.9": ["infuriates"], "0.0 3.5 2.7": ["appraising"], "5.3 14.6 4.6": ["humiliations"], "14.8 19.3 7.1": ["mindlessly"], "1.8 12.6 -2.7": ["postulated"], "12.0 4.6 6.1": ["paean"], "4.9 10.7 23.3": ["falafel"], "11.3 21.5 34.3": ["grubs"], "3.7 11.6 18.8": ["lineouts"], "4.2 18.9 3.4": ["premonition"], "12.8 7.2 9.4": ["decorates"], "3.3 5.1 17.8": ["partiers"], "3.0 5.5 11.8": ["duvet"], "3.8 4.7 5.9": ["yourselfers"], "10.6 16.9 5.4": ["unremitting"], "-6.7 8.5 2.6": ["enunciated"], "2.2 10.9 2.3": ["cordons"], "3.3 6.8 5.1": ["climaxes"], "12.0 14.7 11.3": ["mashing"], "9.0 9.0 6.8": ["ludicrously"], "0.8 6.2 6.2": ["motherly", "diuresis"], "6.6 -5.0 4.9": ["intros"], "8.7 8.3 12.7": ["vid"], "1.7 9.1 4.2": ["nonlinear"], "6.3 5.3 5.0": ["nostril"], "-2.9 3.8 8.6": ["rangebound"], "14.6 3.7 15.8": ["yellowish"], "-6.8 7.5 7.6": ["unvaccinated"], "3.8 5.2 2.3": ["teared"], "21.0 12.7 8.9": ["smiley"], "12.2 0.4 5.5": ["nous"], "0.7 10.8 6.9": ["forethought"], "-3.3 4.6 7.5": ["reinjured"], "4.2 -0.5 0.8": ["underwrites"], "9.0 1.8 6.2": ["chirpy"], "2.9 1.3 4.2": ["comparably"], "-3.6 9.7 6.5": ["aggravates"], "14.9 2.6 3.2": ["plastering"], "12.8 5.2 0.6": ["hummed"], "1.8 4.3 0.0": ["fidgety"], "-0.1 2.6 6.8": ["orgasms"], "3.2 11.1 3.4": ["backswing"], "13.5 -4.3 -0.9": ["dowdy"], "11.7 6.9 2.7": ["droning"], "1.0 5.4 10.1": ["virtualize"], "-1.0 12.5 -1.9": ["westerns"], "1.6 6.0 17.0": ["kilns"], "-5.5 -5.9 12.4": ["afterschool"], "-6.3 9.6 11.8": ["cisplatin"], "17.8 5.0 18.3": ["gluttony"], "2.3 19.7 5.7": ["demagogue"], "-4.7 6.6 19.3": ["caulk"], "4.7 4.5 0.2": ["copywriter"], "9.3 14.8 6.0": ["mavericks"], "-1.7 -5.4 4.4": ["regularization"], "4.7 10.8 20.6": ["lowland"], "3.6 12.6 8.8": ["cached"], "-0.3 4.1 7.4": ["niacin"], "-6.1 6.0 14.8": ["emcees"], "-1.7 10.3 3.6": ["disincentives"], "4.6 5.0 4.4": ["montages"], "11.4 22.9 10.5": ["thusly"], "-2.3 8.0 6.4": ["impersonations"], "-5.3 13.9 11.8": ["hoon"], "9.3 21.0 8.5": ["inhabitant"], "5.0 9.4 4.9": ["gettin"], "7.8 3.5 4.3": ["reeked"], "-0.6 19.5 3.9": ["mullah"], "5.3 14.3 2.0": ["manifesting"], "8.7 13.9 4.7": ["outmuscled"], "-0.4 13.7 8.1": ["backbench"], "-4.5 19.4 3.6": ["mindedness"], "-8.1 35.4 7.8": ["noncombatants"], "13.0 17.3 23.0": ["woodpecker"], "-1.4 0.1 -0.7": ["submarket"], "11.4 12.9 -0.0": ["pillaged"], "2.0 12.6 10.3": ["taxpaying"], "4.7 7.8 9.0": ["kidded"], "-1.2 30.0 11.3": ["sortie"], "20.2 5.1 16.2": ["overhanging"], "18.8 11.4 11.2": ["pocked"], "8.8 1.4 7.3": ["sidesteps"], "0.4 9.8 6.4": ["ther"], "2.5 9.7 9.4": ["oxidized"], "12.0 18.9 4.3": ["untamed"], "10.5 5.1 10.4": ["cresting"], "8.3 7.2 10.4": ["dongle"], "8.6 7.7 14.2": ["mirth"], "-5.5 4.4 7.9": ["intonation"], "1.4 8.0 -0.1": ["preempted"], "8.7 3.9 3.3": ["castrated"], "5.5 10.8 10.9": ["vowels"], "4.1 19.1 10.0": ["dreadfully"], "2.0 6.3 13.3": ["barbed"], "9.6 12.6 14.6": ["entanglements"], "4.6 9.2 -1.9": ["discriminated"], "-3.2 1.9 12.9": ["vegetarianism"], "14.7 18.9 11.2": ["sorcery"], "-2.9 7.8 1.1": ["recollect"], "2.1 7.9 16.6": ["gemstone"], "6.1 5.0 30.0": ["sesame"], "-3.3 8.5 -2.6": ["commited"], "5.2 9.3 10.2": ["kneeled"], "14.6 11.4 4.0": ["minder"], "0.5 3.7 38.6": ["chives"], "-1.6 8.7 8.5": ["oscillator"], "8.5 14.3 12.8": ["tectonic"], "8.9 11.2 16.9": ["buttered"], "3.4 -0.6 10.8": ["hosiery"], "14.2 7.3 20.8": ["isles"], "6.0 9.6 7.6": ["puncturing"], "4.4 14.6 3.9": ["commiserate"], "-0.2 -1.7 0.4": ["irk"], "8.2 8.5 20.9": ["tablecloth"], "-8.2 13.8 1.3": ["goalscorers"], "2.5 5.6 -0.1": ["spectra"], "1.8 17.3 2.1": ["pushovers"], "-6.9 8.7 5.6": ["anesthetics"], "6.5 4.9 -0.5": ["overreached"], "13.8 6.0 11.3": ["unwrap"], "14.2 14.3 9.9": ["apparition"], "6.1 24.0 11.1": ["ploys"], "8.1 10.0 14.0": ["mr"], "5.9 11.9 4.1": ["exemplar"], "12.6 11.8 12.2": ["pharaoh"], "3.5 17.4 4.1": ["frailties"], "6.6 13.9 6.3": ["tandems"], "9.9 9.9 10.7": ["slits"], "9.1 11.2 8.3": ["rivets"], "2.2 8.9 14.0": ["clasp"], "4.8 27.8 8.5": ["heretics"], "-3.4 23.1 4.3": ["causality"], "17.6 19.6 16.1": ["mugger"], "-1.8 5.8 10.6": ["tunics"], "16.5 -1.2 15.1": ["kitchenware"], "-3.6 0.7 2.5": ["readmission"], "2.8 9.2 10.2": ["aways"], "-1.0 5.6 1.1": ["flighted"], "10.9 8.2 5.1": ["unlikeliest"], "4.5 11.7 15.7": ["bloop"], "-14.3 -0.3 0.3": ["repped"], "5.3 3.0 6.8": ["sunnier"], "10.9 3.2 22.1": ["cupola"], "7.0 15.8 4.9": ["brimstone"], "-2.8 -4.5 16.5": ["ketamine"], "11.1 10.6 7.3": ["frothing", "indo"], "4.9 1.4 -4.2": ["mainstreaming"], "1.6 8.6 9.7": ["crestfallen"], "15.0 7.8 4.6": ["hmmm"], "5.5 7.6 7.1": ["interleukin"], "18.5 8.6 24.2": ["toothpicks"], "-1.5 3.0 3.1": ["optimizations"], "5.7 5.2 15.3": ["sightseers"], "9.5 3.4 8.5": ["gobsmacked"], "-1.4 7.8 -1.2": ["pardoning"], "-0.1 4.3 1.6": ["utero"], "10.9 2.7 15.5": ["sate"], "2.6 6.7 8.4": ["curler"], "4.8 0.1 11.1": ["reattach"], "7.2 5.9 46.5": ["calamari"], "-1.6 15.0 2.8": ["misogynistic"], "0.0 0.9 12.5": ["brownstone"], "5.6 16.2 -2.1": ["pacified"], "17.0 4.1 9.2": ["bathtubs"], "-6.2 6.2 -3.6": ["paged"], "7.8 18.2 13.4": ["quicks"], "0.2 0.7 7.2": ["mmscmd"], "7.3 -5.0 8.0": ["cert"], "13.7 8.1 6.4": ["slitting"], "12.2 1.6 -4.4": ["enticements"], "5.7 10.3 0.7": ["endorphins"], "3.3 8.2 0.8": ["rededication"], "6.1 7.0 19.2": ["oxen"], "0.9 16.4 9.4": ["unpleasantness"], "2.4 15.1 13.2": ["butchery"], "3.1 13.1 3.1": ["dint"], "1.8 2.7 6.6": ["sitar"], "6.9 7.9 -1.3": ["proofed"], "3.3 4.2 -6.5": ["committment"], "10.3 18.0 4.8": ["inexhaustible"], "6.5 1.1 9.4": ["syrupy"], "-2.3 10.5 11.8": ["fatherless"], "-1.3 2.8 2.9": ["getters"], "16.4 3.3 3.4": ["corrals"], "1.7 1.8 12.2": ["lengthier"], "6.6 8.9 10.7": ["preorder"], "16.2 0.1 8.1": ["div"], "6.7 7.7 2.0": ["unglamorous"], "7.0 10.5 10.1": ["householder"], "11.1 9.7 25.7": ["beaks"], "1.6 8.5 -4.4": ["reimbursable"], "4.4 12.3 9.1": ["strangeness"], "2.6 10.6 8.2": ["murmured"], "1.4 10.1 -1.3": ["condones"], "7.2 22.1 7.3": ["colonizers"], "5.8 2.3 6.0": ["grungy"], "-1.6 17.7 4.2": ["virulence"], "1.3 -0.6 0.9": ["lumbar"], "-3.0 -1.2 4.6": ["timescales"], "-3.2 4.8 4.6": ["annotations"], "9.0 10.3 35.6": ["salamanders"], "2.3 9.9 -1.5": ["magnitudes"], "-2.1 1.4 -1.0": ["enforceability"], "10.1 13.5 3.6": ["howler"], "6.0 -2.4 9.3": ["baggies"], "2.6 -2.4 1.4": ["repays"], "5.2 22.9 8.1": ["contemptible"], "5.1 28.6 -3.0": ["propagandist"], "7.0 8.9 6.2": ["menial"], "-10.5 0.3 7.6": ["institutionalization"], "3.6 6.8 42.9": ["filet"], "-7.0 10.5 3.0": ["expunge"], "0.4 4.6 4.0": ["validly"], "22.6 15.4 33.0": ["acorn"], "8.8 4.9 9.4": ["disgorgement"], "-7.2 17.7 8.2": ["outwork"], "16.3 8.7 15.1": ["largess"], "7.6 4.0 13.3": ["craigslist"], "3.7 0.1 4.0": ["orthodontist"], "-8.9 3.9 3.6": ["transacting"], "0.1 2.2 9.5": ["buttock"], "1.1 13.2 9.3": ["imbalanced"], "13.9 -0.2 15.1": ["plunking"], "8.0 8.1 8.7": ["repeals"], "16.7 19.9 7.9": ["capitalistic"], "-8.5 8.8 3.6": ["debrief"], "5.5 2.7 32.0": ["cornmeal"], "4.7 13.6 12.3": ["vamp"], "8.2 17.4 15.2": ["squall"], "-4.7 -1.0 18.2": ["bartending"], "14.8 3.9 9.6": ["geysers"], "11.7 4.2 12.7": ["croissants"], "8.6 6.5 4.4": ["constructor"], "9.3 3.0 9.1": ["showstopper"], "3.8 19.0 6.4": ["elusiveness"], "14.1 2.1 -2.6": ["stampeded"], "-1.5 -1.3 14.7": ["listeriosis"], "3.8 8.2 9.0": ["housebuilders"], "8.6 10.7 7.1": ["warren"], "-1.4 3.2 5.2": ["dwelled"], "-3.0 1.2 11.1": ["myelin"], "-0.9 18.9 12.9": ["cuss"], "13.0 4.6 4.5": ["fevered"], "5.6 10.4 12.1": ["rootkit"], "-2.7 20.3 -4.1": ["indoctrinate"], "15.9 25.1 2.0": ["impregnable"], "6.1 13.4 6.3": ["letup"], "-4.7 7.3 1.2": ["fibrosis"], "11.1 14.4 10.9": ["hooligan"], "6.0 -3.4 7.4": ["symposia"], "9.2 11.5 8.5": ["trackpad"], "21.7 23.2 24.2": ["wasp"], "7.1 10.3 -0.2": ["exclaiming"], "5.5 6.9 19.4": ["freckles"], "3.7 15.4 0.9": ["qualitatively"], "13.3 8.5 3.2": ["shudders"], "-5.2 5.8 7.6": ["prepress"], "13.0 3.6 1.0": ["fleecing"], "-3.9 13.6 6.4": ["bloodstains"], "8.7 11.6 13.5": ["littlest"], "3.9 2.6 11.5": ["clubbers"], "10.3 -1.6 4.8": ["gaga"], "5.0 3.3 3.2": ["famer"], "8.9 11.0 5.5": ["decommission"], "0.3 7.8 25.7": ["millet"], "10.2 3.4 16.7": ["girders"], "-5.1 9.1 14.5": ["livability"], "5.2 12.7 18.4": ["goofball"], "0.8 0.4 -0.2": ["weightage"], "-1.4 6.7 2.4": ["immigrating"], "13.7 1.5 8.6": ["backpedaled"], "-0.6 13.1 10.4": ["pastoralists"], "-1.3 3.5 6.3": ["babysitters"], "4.5 10.7 7.7": ["unrevised"], "-10.3 -1.3 8.5": ["fentanyl"], "2.5 5.2 -1.2": ["breathable"], "20.8 11.9 6.4": ["monopolizing"], "8.3 17.8 13.4": ["irrationality"], "3.7 3.9 17.5": ["wallboard"], "-1.6 9.0 8.1": ["debilitated"], "1.5 12.7 7.1": ["delineating"], "13.8 7.4 16.3": ["rancid"], "5.1 5.2 3.6": ["arbiters"], "7.2 15.4 12.0": ["speedsters"], "-2.9 7.7 1.5": ["soldiered"], "-2.0 4.2 16.1": ["mason"], "12.4 11.5 8.8": ["dame"], "10.2 8.1 19.6": ["picker"], "4.5 5.3 23.6": ["weir"], "13.6 7.8 2.1": ["signposts"], "-0.7 15.6 4.5": ["ayatollah"], "18.0 6.1 5.6": ["bungle"], "2.0 2.7 0.5": ["quieting"], "29.9 15.0 4.9": ["silhouetted"], "1.5 14.7 13.8": ["commoners"], "15.0 8.1 13.6": ["spiers"], "-0.2 -3.8 3.8": ["brainstormed"], "-0.8 7.1 9.2": ["octave"], "11.9 22.2 7.9": ["bashers"], "4.5 13.9 17.0": ["tailgaters"], "-1.9 7.8 10.3": ["assortments"], "13.4 10.3 2.2": ["mutilating"], "10.1 2.6 9.7": ["troubadour"], "14.4 3.2 15.4": ["floodlit"], "3.7 19.2 0.1": ["assimilating"], "-8.9 3.1 8.4": ["arrestees"], "2.7 -4.8 -5.3": ["refurbishments"], "5.0 13.0 7.3": ["steadiness"], "11.5 9.6 6.3": ["tidings"], "-2.4 8.6 -3.7": ["uncompromised"], "10.1 15.1 11.0": ["snarls"], "2.9 17.1 8.9": ["olfactory"], "4.5 7.6 8.1": ["knockoffs"], "2.2 4.0 -0.6": ["skittled"], "-1.8 12.4 -1.7": ["pseudonyms"], "6.7 17.3 7.9": ["appallingly"], "-4.6 7.3 4.1": ["epidural"], "-3.9 6.8 -3.1": ["pathogenesis"], "-2.4 19.5 4.4": ["diss"], "8.8 9.1 8.8": ["hooting"], "2.7 0.6 9.4": ["closeout"], "5.5 12.0 33.5": ["osprey"], "21.8 18.2 16.2": ["mothership"], "3.7 19.5 21.0": ["pollinators"], "23.2 9.8 -0.4": ["whirring"], "-3.1 4.2 0.1": ["docudrama"], "6.1 4.3 31.5": ["kimchi"], "17.6 4.6 6.4": ["convulsed"], "0.3 -2.5 8.7": ["mementoes"], "-0.1 10.1 7.8": ["flyweight"], "-0.8 3.4 10.5": ["tuneful"], "3.9 12.4 26.9": ["topside"], "15.1 11.9 8.4": ["hurls"], "-5.7 2.6 15.7": ["telomeres"], "4.6 4.7 5.2": ["saccharine", "girlband"], "-3.0 4.6 8.1": ["kwh"], "0.1 13.5 7.2": ["neurotransmitters"], "8.9 10.8 3.7": ["chummy"], "6.2 -1.0 12.7": ["derivation"], "6.7 10.4 5.7": ["nanotube"], "-2.2 8.3 5.1": ["councilmember"], "1.9 10.6 17.4": ["buffaloes"], "22.0 9.8 8.9": ["belching"], "-1.7 4.6 2.3": ["sportscar"], "5.2 35.0 2.4": ["bombardments"], "-2.3 23.4 -1.2": ["conscripted"], "14.8 4.8 16.1": ["rotund"], "1.8 8.7 6.1": ["outhustled"], "7.5 10.6 2.4": ["schematics"], "10.0 5.8 10.1": ["coddled"], "23.2 4.6 17.4": ["globes"], "4.9 6.4 11.0": ["flywheel"], "-2.0 10.6 2.5": ["embargoed"], "11.1 2.1 11.7": ["housings"], "6.5 18.6 2.4": ["classless"], "8.6 12.3 8.8": ["ppl"], "6.9 2.6 16.2": ["flannel"], "13.0 7.5 8.9": ["churlish"], "10.8 14.3 5.2": ["eliminator"], "9.2 0.0 5.5": ["practicalities"], "-2.3 17.8 0.0": ["tasking"], "7.7 1.6 7.6": ["york"], "-0.8 6.3 7.2": ["inoculations"], "-5.4 2.7 5.2": ["alumnae"], "0.8 7.1 14.7": ["clippers"], "-1.8 13.0 20.5": ["barbecuing"], "19.3 4.0 5.7": ["mavens"], "1.2 8.9 0.6": ["reiteration"], "-4.9 4.8 4.9": ["womenswear"], "-4.9 6.4 3.7": ["outpointed"], "-1.9 2.5 25.0": ["casseroles"], "-0.9 1.3 -1.0": ["upliftment"], "8.1 12.3 5.5": ["prods"], "12.6 9.7 9.2": ["indian"], "3.3 5.2 11.5": ["entertainments"], "-1.3 5.6 4.8": ["steppingstone"], "11.3 4.4 5.5": ["receptionists"], "-1.9 2.0 8.6": ["callback"], "15.5 13.8 11.0": ["scowling"], "-4.6 10.8 0.7": ["idolize"], "-7.3 19.0 11.3": ["lovemaking"], "-0.0 5.4 0.8": ["percolate"], "10.0 3.7 28.8": ["meringue"], "11.7 13.5 4.6": ["yapping"], "-1.5 2.2 7.6": ["marathoners"], "0.7 -8.4 3.8": ["adjourns"], "7.4 0.1 3.2": ["biosciences"], "3.1 14.7 -0.3": ["incognito"], "-1.7 -5.9 26.0": ["pedicures"], "2.1 9.1 5.9": ["yeoman"], "-1.7 -1.7 -0.7": ["abolishment"], "9.1 13.2 10.0": ["golly"], "9.0 15.8 2.9": ["pretender"], "-5.4 1.8 9.6": ["nonprescription"], "14.3 4.8 7.8": ["rustle"], "3.9 13.3 6.0": ["hallucinating"], "4.7 3.4 6.6": ["penthouses"], "-1.8 6.5 7.8": ["oxides"], "-1.7 17.7 -0.1": ["affirmatively"], "-6.9 14.0 8.5": ["toeing"], "13.2 7.3 15.4": ["tarpaulin"], "17.4 24.8 21.6": ["snot"], "6.8 10.6 13.6": ["slapper"], "9.6 0.9 8.6": ["redolent"], "15.5 4.6 16.4": ["yuppie"], "-6.0 12.6 6.8": ["dramatist"], "13.1 7.1 7.2": ["effigies"], "11.1 7.9 38.7": ["artichoke"], "8.3 15.9 11.4": ["lobs"], "9.1 10.4 3.3": ["burrowed"], "1.4 6.3 3.7": ["slurring"], "8.1 0.5 24.6": ["stewed"], "3.6 9.7 4.9": ["silencer"], "1.8 14.8 8.0": ["pettiness"], "8.8 0.9 0.5": ["lather"], "9.5 9.1 8.0": ["snuffing"], "7.7 12.1 13.1": ["irascible"], "8.5 6.1 9.6": ["poncho"], "8.0 7.9 -2.8": ["outsell"], "1.5 9.6 58.9": ["crabbing"], "8.2 -1.1 3.9": ["sagas"], "-6.3 10.6 10.1": ["jayvee"], "-5.0 4.2 5.8": ["resentencing"], "5.4 17.5 20.2": ["sp"], "6.7 36.5 10.0": ["infantrymen"], "-4.2 5.5 2.2": ["billable"], "1.0 35.4 1.0": ["apostates"], "8.6 11.2 7.4": ["overachieving"], "9.9 10.3 12.6": ["cuteness"], "4.3 9.3 12.8": ["raincoat"], "7.0 19.9 7.7": ["subduing"], "9.5 13.3 7.7": ["sages"], "13.0 -1.1 6.8": ["reigniting"], "5.6 4.8 5.0": ["rollbacks"], "-2.1 16.0 6.1": ["directness"], "11.0 12.7 13.2": ["earthen"], "4.4 3.1 17.6": ["eastside"], "-8.9 2.3 13.7": ["biosolids"], "2.1 8.4 15.4": ["stalemated"], "3.2 6.5 11.7": ["sooo"], "8.6 2.5 3.5": ["wheelbarrows"], "11.2 15.7 4.6": ["cowered"], "-4.5 4.5 1.9": ["elucidate"], "0.6 3.9 -0.9": ["breech"], "12.9 6.4 17.7": ["lengthwise"], "14.2 12.1 12.4": ["chaining"], "-1.7 3.9 6.7": ["kinase"], "15.6 -4.4 12.8": ["heftier"], "0.9 3.4 9.8": ["carburetor"], "1.6 1.5 -2.2": ["nodal"], "7.8 8.4 9.6": ["skewering"], "14.0 23.0 15.7": ["goon"], "8.0 2.5 6.7": ["separator"], "2.6 8.9 3.3": ["grittier"], "0.7 15.3 10.3": ["constabulary"], "10.7 15.4 32.9": ["raptor"], "8.4 6.0 12.3": ["gigahertz"], "9.6 10.8 10.0": ["northwards"], "7.5 3.3 11.8": ["restocked"], "-1.7 5.5 -0.5": ["edema"], "14.4 17.5 15.4": ["cripples"], "6.5 14.8 5.9": ["psyches"], "3.0 10.4 4.9": ["transcendence"], "9.1 13.5 24.6": ["crumb"], "16.4 11.8 26.8": ["feathery"], "4.6 11.2 -3.2": ["systemically"], "8.7 12.2 9.8": ["workmates"], "8.4 4.6 13.5": ["dicing"], "9.1 3.2 12.8": ["loafers"], "2.9 16.2 6.7": ["taciturn"], "-2.7 5.3 9.9": ["embalming"], "-1.8 12.6 20.6": ["seaplane"], "4.9 8.6 -0.0": ["chides"], "-0.9 10.3 2.9": ["lessees"], "-0.5 10.3 12.4": ["kneed"], "10.3 9.9 10.6": ["detente"], "-7.2 2.8 5.5": ["expound"], "-3.4 9.7 14.8": ["jaywalking", "pagod"], "4.6 8.3 7.0": ["rightfield"], "6.0 6.8 -2.2": ["blacking"], "3.5 8.5 -0.6": ["ruggedness"], "2.3 2.4 8.9": ["saturday"], "-0.9 8.0 7.4": ["leftfielder"], "3.3 9.0 -3.5": ["inspectorate"], "7.0 9.0 8.7": ["shanked"], "6.7 18.9 -0.5": ["undying"], "10.0 9.1 17.1": ["deadbeat"], "-7.6 2.8 14.8": ["quintal"], "7.2 11.3 3.6": ["breathtakingly"], "3.8 20.1 8.9": ["jammers"], "-9.4 -2.4 7.3": ["anthologies"], "7.4 3.2 10.6": ["photoshop"], "-7.6 -0.7 7.8": ["reauthorized"], "17.5 16.7 6.8": ["crevice"], "1.7 10.4 3.1": ["birther"], "5.3 5.3 0.0": ["enjoin"], "3.7 21.5 1.6": ["outmanned"], "10.5 29.5 7.2": ["henchman"], "-7.1 0.2 -4.0": ["ministered"], "-12.3 11.4 13.7": ["varietal"], "19.2 16.0 6.4": ["aflame"], "4.9 7.7 12.6": ["peewee"], "-1.4 8.0 3.4": ["neurobiology"], "0.5 -3.0 12.8": ["tapers"], "-2.6 6.3 10.2": ["drinkable"], "4.7 9.5 10.8": ["grammatical"], "15.4 0.4 4.0": ["toppers"], "1.1 7.3 8.5": ["choreographing", "overpitched"], "8.1 15.5 11.2": ["sameness"], "1.1 8.0 -0.3": ["inspite"], "3.2 3.6 1.4": ["querying"], "-0.6 3.7 21.4": ["ganja"], "-6.3 -1.5 6.6": ["headwear"], "13.0 14.8 11.4": ["thieving"], "20.8 7.0 4.9": ["conglomeration"], "-4.9 8.3 2.8": ["didactic"], "-0.6 4.5 6.8": ["segregating"], "-0.3 12.8 19.1": ["mealtime"], "0.9 7.8 14.4": ["tonsils"], "-3.2 11.9 7.9": ["despondency"], "4.9 3.7 2.2": ["sensationalized"], "0.4 11.3 4.9": ["tourniquet"], "11.2 13.2 4.9": ["vainly"], "-5.8 5.9 33.8": ["shallots"], "23.5 3.2 10.5": ["whirled"], "-6.7 4.1 29.2": ["chickpeas"], "9.4 22.2 9.9": ["bludgeon"], "4.4 9.0 0.5": ["undrawn"], "22.9 21.9 8.8": ["maniacs"], "0.1 7.7 7.6": ["unhygienic"], "12.0 5.7 2.8": ["rebuffs"], "3.5 16.6 13.3": ["recrimination"], "-1.4 6.8 10.9": ["laminitis"], "3.0 4.0 10.4": ["fairing"], "8.2 3.4 22.3": ["cobbler"], "3.5 4.0 11.4": ["bathrobe"], "-1.3 9.7 10.1": ["offhand"], "9.2 3.9 10.3": ["schmoozing"], "4.7 10.0 6.8": ["loanee"], "-5.4 11.9 -0.3": ["impeaching"], "-1.0 -1.0 14.6": ["denosumab"], "13.0 11.8 15.9": ["koalas"], "-12.1 3.2 3.7": ["congregational"], "-7.6 2.5 15.0": ["heirlooms"], "-7.3 2.6 1.9": ["obstetric"], "3.2 3.7 13.2": ["fastidious"], "-0.1 10.5 -3.0": ["reorganizations"], "-3.3 -4.1 1.7": ["demographers"], "-2.0 5.2 11.9": ["timbre"], "-1.9 6.3 10.4": ["inpatients"], "8.4 0.0 0.4": ["professorship"], "-1.2 0.1 18.1": ["cox"], "12.8 1.0 4.2": ["reclaims"], "-3.8 18.5 0.0": ["sympathizing"], "-4.3 4.9 6.2": ["streetwise"], "9.0 3.4 9.9": ["zookeeper"], "22.5 3.3 8.7": ["toasters"], "1.0 11.4 11.2": ["betters"], "6.4 3.9 7.6": ["lovelorn"], "5.2 -3.4 21.3": ["zesty"], "-0.9 1.0 10.6": ["raspy"], "5.1 14.3 9.2": ["unachievable"], "-2.8 19.0 8.9": ["opportunistically"], "12.6 3.7 10.9": ["ratchets"], "11.5 7.2 5.2": ["grimmer"], "3.3 1.3 -1.2": ["turbochargers"], "19.0 10.2 14.1": ["shimmy"], "1.5 -3.9 7.7": ["waxes"], "3.2 3.0 8.5": ["grousing"], "0.9 16.7 6.5": ["countervailing"], "4.6 8.5 7.1": ["procrastinating"], "3.9 10.4 13.5": ["armpits"], "17.3 11.9 10.0": ["nimbly"], "-3.7 23.7 -0.6": ["detachments"], "1.8 9.9 14.6": ["innkeeper"], "7.1 13.5 9.2": ["exclaim"], "-2.8 -9.7 4.3": ["lactation"], "11.3 5.8 5.8": ["yesterdays", "socialmedia"], "21.4 6.9 12.0": ["ungainly"], "18.7 7.9 14.8": ["jut"], "0.9 -1.5 0.2": ["rehashed"], "4.3 -1.7 6.9": ["nonrefundable"], "0.0 13.0 7.5": ["filmgoers"], "5.5 17.2 17.4": ["seaborne"], "0.4 -1.8 0.3": ["handbooks"], "-0.4 13.6 49.0": ["lobstermen"], "0.7 3.6 21.4": ["exotics"], "-0.4 7.2 10.7": ["croon"], "4.4 7.6 3.3": ["havent"], "-2.1 2.5 17.3": ["nutritionally"], "3.3 5.1 4.6": ["irregularly"], "-1.4 6.7 0.3": ["decertified"], "-5.1 0.2 3.9": ["uncompressed"], "-1.4 7.7 -4.7": ["vulgarities"], "10.2 -4.9 11.2": ["plumped"], "6.9 7.0 5.7": ["fidgeting"], "13.9 15.0 4.9": ["vaporized"], "0.9 3.5 -2.4": ["predispose"], "2.6 9.0 4.9": ["regretfully"], "4.9 16.1 15.2": ["webbing"], "-1.3 11.9 7.5": ["beryllium"], "3.3 12.3 8.7": ["trekkers"], "-4.4 -7.4 2.9": ["homemakers"], "15.8 6.7 2.5": ["flashier"], "13.4 6.7 29.6": ["driftwood"], "6.0 7.9 3.7": ["underpowered"], "-3.7 13.5 14.0": ["houseplants"], "-8.7 1.4 6.2": ["anesthesiology"], "15.8 1.9 2.7": ["rewiring"], "7.6 16.8 14.7": ["ump"], "-0.5 21.7 9.0": ["viciousness"], "9.5 2.3 10.6": ["randy"], "1.9 3.6 8.1": ["flamboyance"], "16.5 8.1 11.0": ["colorfully"], "12.6 9.8 8.2": ["lullaby"], "1.4 -2.0 2.6": ["toolkits"], "4.3 11.5 9.0": ["flushes"], "-11.1 -1.3 -4.5": ["rearrested"], "10.8 8.4 2.3": ["supercenter"], "8.1 17.6 3.3": ["paradoxes"], "8.9 4.4 7.9": ["oohs"], "1.0 7.2 9.5": ["adulteration"], "14.9 2.7 10.6": ["surfeit"], "-5.2 8.0 0.3": ["hyperthermia"], "18.3 5.1 12.6": ["swishing"], "4.7 4.7 4.4": ["blinkx"], "23.2 16.7 23.6": ["crawler"], "8.9 -0.5 10.7": ["planed"], "10.3 6.2 8.5": ["resurfaces"], "-1.5 13.1 9.7": ["moviegoing"], "7.5 8.6 1.5": ["rectification"], "-8.9 7.8 7.4": ["medaled"], "6.5 8.6 4.8": ["thinktank"], "-0.8 -0.3 7.9": ["conserves"], "0.4 12.9 7.7": ["engenders"], "7.7 22.8 20.4": ["crewmember"], "10.2 5.9 2.6": ["snuggled"], "4.1 15.9 10.2": ["vagrants"], "1.4 10.3 25.3": ["waders"], "-0.7 18.4 11.2": ["pathogenic"], "3.5 7.9 4.1": ["arent"], "13.5 -1.5 2.7": ["pricked"], "12.5 7.1 9.8": ["hmm"], "9.4 14.2 4.7": ["weeps"], "-0.5 8.1 11.5": ["domestics"], "-2.8 12.7 -8.4": ["incriminate"], "18.3 3.8 11.6": ["bejeweled"], "5.4 16.4 -4.9": ["codename"], "3.0 4.4 14.9": ["scarcer"], "0.8 12.4 2.0": ["fixable"], "2.4 4.5 2.7": ["gradation"], "-4.7 16.8 1.9": ["precept"], "9.6 4.9 -0.4": ["collating"], "4.8 8.8 7.2": ["pronounces"], "6.0 19.8 5.5": ["provocateur", "theologizing"], "4.3 12.3 8.8": ["astoundingly"], "10.4 5.4 17.7": ["bayous"], "-3.8 11.8 7.2": ["representational"], "-5.2 1.6 12.0": ["whitening"], "1.6 19.3 3.2": ["kidnaps"], "4.9 7.9 7.2": ["astrologers"], "-13.0 1.5 5.8": ["stillbirth"], "4.9 5.8 11.0": ["dykes"], "5.0 4.0 1.4": ["turbocharger"], "16.0 7.4 28.0": ["pasty"], "3.1 11.5 0.4": ["tasered"], "17.4 5.2 14.5": ["sandpaper"], "22.0 9.6 9.9": ["pushers"], "12.8 15.5 0.1": ["unmask"], "7.0 9.0 5.7": ["sleepless"], "3.2 7.7 3.4": ["cannibalizing"], "8.0 5.6 6.1": ["stereoscopic"], "11.0 8.7 13.5": ["tenderly"], "-7.1 -1.5 4.2": ["honorarium"], "3.6 16.9 7.9": ["imperfection"], "9.7 7.3 9.9": ["granules"], "6.8 2.5 8.3": ["impersonators"], "18.5 -0.9 -0.4": ["multimillion"], "14.1 15.1 10.0": ["busters", "straightfaced"], "4.6 2.1 7.7": ["bodybuilders"], "15.5 8.3 9.2": ["cutie"], "11.4 7.5 7.5": ["plinth"], "-0.8 16.1 14.1": ["enumeration"], "16.9 12.7 3.3": ["pivoting"], "6.8 14.2 33.1": ["spearing"], "2.8 6.4 0.4": ["spectrometer"], "0.6 9.3 4.8": ["correlating"], "1.1 13.3 17.7": ["bunkering"], "11.7 2.1 6.5": ["bricklayer"], "-5.9 8.1 11.3": ["proration"], "-1.3 6.8 5.7": ["lapels"], "1.7 9.3 6.1": ["soooo"], "-1.1 11.6 5.2": ["brusque"], "5.3 2.2 12.2": ["statehouses"], "5.6 30.7 7.3": ["renegades"], "6.2 0.6 12.0": ["gnashing"], "4.7 6.3 3.2": ["trivialize"], "5.7 8.0 3.4": ["cosmology", "surviellance"], "17.7 14.2 14.4": ["supertanker"], "-1.4 -4.3 11.7": ["pickings"], "7.5 13.8 10.6": ["hardens"], "7.4 4.2 12.0": ["mu"], "5.6 4.3 6.2": ["weepy"], "9.7 12.7 2.7": ["diktat"], "3.2 6.0 10.9": ["basal"], "2.2 15.5 12.3": ["underbrush"], "-3.7 -0.8 1.4": ["physios"], "13.6 8.8 6.9": ["filaments"], "5.5 6.1 4.1": ["sickens"], "10.7 1.5 16.3": ["girder"], "-3.8 -4.9 12.0": ["genotyping"], "1.2 14.3 13.7": ["scrummaging"], "8.9 16.4 14.1": ["devises"], "-5.0 2.8 0.1": ["peroxide"], "11.1 9.0 8.8": ["inflates"], "7.2 9.1 7.0": ["stickiness"], "4.5 7.1 13.0": ["bluesman"], "5.0 8.2 -2.3": ["wishlist"], "5.4 4.5 9.3": ["fess"], "2.5 6.7 14.4": ["caroms"], "2.3 12.8 8.9": ["pretension"], "1.7 3.8 6.4": ["vertebra"], "5.8 8.2 4.4": ["carping"], "1.6 1.1 14.0": ["pawnshop"], "3.2 1.5 2.4": ["repeatability"], "14.0 10.4 5.1": ["comms"], "1.3 -0.8 -2.3": ["clearinghouses"], "16.1 15.7 4.0": ["uneasily"], "2.3 10.7 11.0": ["harem"], "6.3 8.6 1.3": ["smolder"], "5.3 13.6 11.8": ["gentleness"], "14.6 17.3 14.7": ["nothingness"], "-0.4 10.7 10.8": ["catty"], "5.7 14.6 4.0": ["illicitly"], "1.6 5.1 8.5": ["knitters"], "-1.0 3.2 -0.3": ["ford"], "4.4 13.6 8.0": ["furtive"], "15.1 -0.2 8.4": ["zippy"], "2.2 6.6 10.8": ["trios"], "11.1 0.6 14.0": ["zookeepers"], "7.8 18.6 12.1": ["rappelling"], "0.2 8.1 10.9": ["galloper"], "0.2 8.6 16.8": ["roadless"], "7.0 -1.1 10.4": ["reg"], "-0.6 14.1 19.6": ["wheelhouse"], "-1.5 3.3 6.2": ["endocrinologist"], "-1.3 -1.9 1.6": ["composes"], "17.2 13.8 12.2": ["blowtorch"], "3.3 11.6 1.9": ["glorifies"], "3.9 0.4 -2.4": ["ratifies"], "7.2 8.7 5.0": ["neuroscientists"], "0.7 -4.9 5.7": ["newsagents"], "13.6 8.3 5.9": ["suckered"], "8.8 9.3 12.8": ["sighing"], "-11.6 0.2 0.6": ["clarinetist"], "1.8 -2.6 32.4": ["ricotta"], "1.1 -0.8 8.7": ["sass"], "18.3 5.1 51.5": ["kelp"], "9.6 4.9 8.2": ["cobbled"], "3.2 40.9 7.3": ["unbelievers"], "6.8 8.3 5.7": ["unglued"], "9.7 3.3 4.4": ["permeating"], "9.4 3.3 11.0": ["curiosities"], "8.7 8.9 6.3": ["scalped"], "15.8 4.9 4.3": ["conveyors"], "-3.4 1.3 4.7": ["tolled"], "15.3 18.2 19.6": ["splatter"], "12.5 1.3 13.9": ["inlaid"], "9.6 11.1 12.7": ["reflector"], "8.0 17.5 6.6": ["socialistic"], "18.2 19.5 8.1": ["brainless"], "4.2 -6.3 9.0": ["compostable"], "4.8 19.7 5.9": ["bugle"], "-6.6 4.9 -1.6": ["methodological"], "5.5 5.6 5.7": ["cyclicality"], "-8.5 0.8 6.6": ["sires"], "9.0 25.6 11.1": ["wimps"], "-8.7 1.5 8.4": ["disbarment"], "5.4 22.2 0.2": ["terrains"], "2.6 4.6 2.6": ["insurances"], "5.1 4.0 36.5": ["quiche"], "1.0 2.8 7.3": ["geologically"], "-1.3 17.3 4.9": ["disconnects"], "11.9 28.7 7.3": ["expansionist"], "-7.2 12.2 4.2": ["linearity"], "3.3 9.4 26.0": ["bobcats"], "2.1 5.9 3.4": ["attains"], "2.1 -3.8 5.3": ["misspellings"], "10.9 10.4 6.3": ["grandad"], "1.9 2.8 7.9": ["copayments"], "8.0 20.5 12.6": ["cruelest"], "6.6 10.3 17.9": ["unnaturally"], "1.9 0.0 11.9": ["loaner"], "4.9 2.4 4.7": ["buffered"], "5.7 12.0 3.5": ["rebooting"], "6.8 2.2 7.1": ["bookcases"], "13.2 5.2 0.4": ["planemaker"], "10.8 18.2 8.7": ["decimation"], "4.5 9.1 10.1": ["readjusted"], "27.1 3.5 5.2": ["boffins"], "8.7 -4.0 4.0": ["db"], "0.2 9.8 11.3": ["eugenics"], "9.1 18.4 33.2": ["shoals"], "-0.5 7.3 7.4": ["gallbladder"], "13.0 8.8 11.5": ["horoscope"], "-5.9 19.0 2.4": ["counternarcotics"], "-4.2 0.1 8.3": ["conformation"], "-0.4 4.8 13.6": ["trotter"], "5.8 4.0 5.9": ["unruffled"], "1.3 5.3 -4.4": ["decertify"], "10.1 7.3 15.3": ["lunchbox"], "6.3 9.5 11.3": ["backbreaking"], "5.7 -0.6 2.6": ["coders"], "-7.4 4.3 10.2": ["colloquial"], "-7.4 3.0 7.2": ["brachytherapy"], "1.9 12.5 15.7": ["pollinate"], "3.5 9.1 29.2": ["sorbet"], "13.1 18.3 12.5": ["craven"], "-0.6 8.6 9.0": ["squeaker"], "10.0 16.3 12.0": ["disbelieving"], "14.6 42.8 2.2": ["archenemy"], "18.0 16.7 11.1": ["symbiotic"], "0.4 5.3 5.2": ["cume"], "9.3 -6.4 8.6": ["kibosh"], "-2.5 32.0 4.4": ["lethality"], "3.0 6.1 13.3": ["surrealism"], "19.1 27.1 21.5": ["orbs"], "1.3 5.3 23.8": ["bonsai"], "23.3 9.5 13.9": ["steamroller"], "2.2 8.0 9.4": ["eyelash"], "-7.6 6.8 -4.9": ["asphyxia"], "-7.8 18.5 9.3": ["officeholder"], "11.2 2.5 0.6": ["cluttering"], "7.7 3.7 14.4": ["bollards"], "5.4 15.2 10.5": ["squalls"], "7.7 5.5 7.7": ["approximates"], "-0.1 24.0 4.2": ["animus"], "3.2 3.8 30.9": ["cashew"], "3.4 1.2 7.9": ["sweepers"], "2.7 6.8 6.4": ["commentating"], "-1.2 6.5 0.7": ["sleepiness"], "0.1 12.8 4.8": ["fourballs"], "8.6 9.9 10.4": ["quacks"], "2.3 -0.8 8.0": ["cancelations"], "0.5 8.5 8.5": ["impressionistic"], "9.1 13.0 4.7": ["guises"], "5.5 0.6 14.4": ["tiling"], "4.0 9.0 3.3": ["chronicler"], "4.9 2.0 10.0": ["journeymen"], "-0.4 9.6 6.4": ["disfigurement"], "7.0 5.3 3.6": ["redoubled"], "4.3 13.9 22.6": ["geisha"], "2.4 21.0 10.0": ["dismount"], "1.4 6.9 4.7": ["givebacks"], "1.9 12.0 6.0": ["discontented"], "9.2 10.4 13.1": ["tweezers"], "2.0 7.2 1.2": ["exhortations"], "-2.2 37.7 5.9": ["treasonous"], "9.4 4.5 7.3": ["scalded"], "17.2 2.3 17.6": ["barnyard"], "3.2 3.3 11.3": ["paycheque"], "3.8 7.6 12.8": ["dynastic"], "1.4 19.5 8.2": ["scapegoating"], "-2.2 8.8 2.1": ["deletes"], "10.3 6.3 7.4": ["hoots"], "20.0 -1.5 6.0": ["multilevel"], "5.6 19.6 9.6": ["playmates"], "15.4 11.5 15.9": ["hippos"], "11.2 2.1 2.4": ["decelerated"], "1.4 2.2 8.5": ["reggaeton"], "9.0 21.8 16.9": ["exterminator"], "5.6 8.8 6.4": ["senile"], "1.0 15.2 7.6": ["gliders"], "-1.3 18.3 8.1": ["unfailingly"], "4.3 5.9 2.8": ["inflight"], "16.2 11.5 22.3": ["leech"], "12.5 6.8 10.3": ["incestuous"], "-0.9 -1.8 7.1": ["corsets"], "-6.6 10.4 13.5": ["apportionment"], "4.5 5.9 6.0": ["slats"], "-2.2 2.8 22.9": ["absinthe"], "3.1 0.7 9.1": ["gastronomy"], "-4.1 20.4 2.4": ["adversities"], "-7.4 11.0 9.5": ["underclassman"], "2.5 -2.3 5.1": ["transducers"], "8.9 7.6 0.6": ["personify"], "1.6 29.6 21.6": ["snipe"], "4.7 15.3 4.9": ["backfiring"], "10.4 12.1 12.3": ["fuckin"], "11.8 5.5 21.3": ["testicle"], "8.0 14.2 8.8": ["wearily"], "-1.6 5.0 10.2": ["laidback"], "1.5 18.1 -2.2": ["ravines"], "8.5 11.0 8.6": ["singalong"], "-1.7 -0.8 3.8": ["bioavailability"], "10.7 5.6 15.6": ["haiku"], "0.9 1.1 11.3": ["trippers"], "1.0 -1.2 1.2": ["detracted"], "8.8 6.9 2.8": ["foist"], "2.9 10.2 14.9": ["stewing"], "6.8 3.4 0.2": ["offeror"], "1.5 3.9 13.6": ["dings"], "5.1 11.2 6.2": ["proton"], "-3.7 4.1 29.1": ["sirloin"], "-7.4 14.4 14.6": ["attackman"], "8.4 9.0 10.4": ["wishbone"], "9.9 14.1 16.5": ["bard"], "-3.3 10.7 2.1": ["unhedged"], "5.8 -6.1 13.8": ["moratoriums"], "4.7 16.8 1.6": ["loyally"], "12.7 18.9 5.8": ["tenaciously"], "16.4 13.5 9.3": ["chieftains"], "16.9 13.0 5.3": ["fiefdom"], "6.7 9.2 4.1": ["recompense"], "2.8 4.7 3.9": ["antimony"], "6.3 7.7 5.5": ["loquacious"], "-3.1 -2.0 -4.4": ["trialists"], "1.3 7.8 6.3": ["fatherly"], "10.4 17.9 3.5": ["commandeer"], "8.5 10.2 2.0": ["byways"], "7.5 2.4 5.4": ["mops"], "7.1 10.2 5.6": ["resize"], "4.5 8.8 14.0": ["subtropical"], "10.0 5.3 16.6": ["sated"], "5.7 5.9 11.7": ["bonhomie"], "8.6 12.4 2.1": ["unlit"], "6.8 2.2 7.7": ["uncertainly"], "-1.5 12.0 0.2": ["quantitatively"], "-7.3 11.5 5.8": ["improvisations"], "23.0 1.7 13.4": ["deliveryman"], "10.4 13.7 9.5": ["groupie"], "9.7 26.6 5.0": ["rabble"], "8.8 12.8 7.3": ["alcove"], "9.4 8.3 11.0": ["backhoes"], "0.1 2.1 20.1": ["grated"], "6.0 7.0 -0.9": ["exhaustively"], "4.3 4.3 10.8": ["disinclined"], "5.7 -1.6 -1.2": ["forints"], "2.4 3.9 13.8": ["feedings"], "13.6 23.1 9.4": ["muggers"], "9.5 5.2 14.6": ["linux"], "11.0 2.4 18.8": ["yuletide"], "16.1 15.2 4.3": ["singlehandedly"], "12.9 3.4 0.7": ["mkt"], "8.7 4.9 11.9": ["tapestries"], "2.3 0.6 17.6": ["carnations"], "7.3 15.9 5.3": ["unknowing"], "17.2 4.0 16.5": ["skinning"], "1.0 4.3 5.2": ["tenterhooks"], "-1.2 3.3 5.3": ["harpist"], "1.1 4.0 10.1": ["proximal"], "5.6 5.6 5.5": ["rediscovery"], "14.1 1.1 3.5": ["shapely"], "5.2 11.5 7.6": ["reorder"], "6.0 2.5 14.3": ["cobbles"], "11.4 10.0 4.4": ["greeters"], "1.0 -2.7 5.2": ["lorcaserin"], "-12.9 3.5 6.1": ["homeschooled"], "0.0 25.0 11.0": ["chivalry"], "-0.2 10.7 12.7": ["prions"], "13.0 1.8 9.2": ["castoffs"], "14.6 4.2 24.4": ["sundae"], "0.5 10.3 3.2": ["attitudinal"], "8.6 7.0 5.4": ["recline"], "11.1 8.0 6.8": ["bloopers"], "7.6 14.2 9.2": ["gasses"], "6.3 15.0 10.5": ["blushing"], "5.9 -6.3 15.1": ["multigenerational"], "2.0 13.4 11.9": ["grappler"], "0.8 17.2 8.2": ["rationales"], "14.3 6.1 23.7": ["hoppers"], "-1.5 10.3 8.2": ["recalculated"], "8.6 9.4 6.9": ["teasers"], "-5.4 5.0 1.9": ["monetarily"], "4.8 20.1 12.2": ["meanness"], "10.6 1.1 2.9": ["passe"], "1.6 5.7 2.0": ["laymen"], "6.9 3.3 7.7": ["nappy"], "11.4 5.0 3.6": ["contoured"], "-5.9 8.4 4.9": ["offseasons"], "-6.8 0.7 -4.3": ["acquitting"], "11.8 12.3 1.2": ["trembled"], "2.9 8.2 27.5": ["omelets"], "8.9 8.1 -2.0": ["obtrusive"], "5.0 13.7 1.8": ["feigning"], "7.5 12.5 9.1": ["curmudgeon"], "-1.1 5.2 14.9": ["frescoes"], "0.9 13.7 3.8": ["corrupts"], "-3.7 5.6 5.6": ["agonize"], "14.3 21.0 0.2": ["zealot"], "-4.5 7.2 6.2": ["seismologist"], "-0.9 25.3 -3.7": ["sympathizer"], "20.9 22.5 25.2": ["hedgehog"], "3.2 14.5 5.6": ["jailbreaking"], "7.9 8.6 11.7": ["wrenches"], "-2.7 -0.6 15.7": ["batik"], "-3.5 4.3 6.0": ["oscillators"], "0.7 1.2 3.0": ["decentralize"], "10.9 8.2 0.6": ["expropriate"], "-5.9 7.6 5.1": ["workover"], "-5.7 4.1 4.2": ["gritted"], "-6.2 3.9 -0.8": ["pendency"], "7.4 21.2 7.8": ["impolite"], "-5.1 -2.1 0.9": ["disposables"], "-0.4 12.0 6.4": ["wideband"], "4.0 22.8 9.7": ["natures"], "11.1 3.3 14.5": ["krona"], "4.7 -2.4 4.5": ["backstopped"], "-0.6 7.2 5.9": ["pigeonholed"], "14.6 -2.6 1.8": ["septuagenarian"], "-4.6 11.3 10.1": ["flavonoids"], "2.4 17.0 -2.6": ["ultimatums"], "7.1 3.4 1.0": ["preinstalled"], "7.5 -1.8 6.1": ["languishes"], "10.8 10.6 5.5": ["mists"], "3.7 -1.7 12.6": ["subsist"], "6.0 7.3 4.8": ["bleakest"], "2.8 2.5 10.9": ["playgroup"], "3.3 2.7 9.9": ["lycopene", "acesulfame"], "18.1 11.1 8.9": ["wands"], "12.5 10.3 -4.4": ["remotest"], "1.6 3.9 2.5": ["watchlist"], "-0.7 17.5 11.5": ["backstabbing"], "15.4 19.2 26.4": ["locust"], "7.6 -0.9 6.0": ["seesawed"], "3.3 10.8 12.0": ["gooder"], "-1.6 14.9 -4.9": ["dishonored"], "-6.1 8.5 3.2": ["canonized"], "-0.2 11.4 3.3": ["subd"], "10.3 7.8 45.3": ["marlin"], "17.0 0.0 3.5": ["outsources"], "4.5 6.5 -3.0": ["sully"], "12.0 10.8 9.1": ["pedestals"], "2.9 14.0 5.7": ["pathologies"], "15.6 0.6 11.6": ["fringed"], "1.6 6.2 10.2": ["anticancer"], "14.1 13.3 5.0": ["clobber"], "8.5 3.3 13.4": ["gorgeously"], "11.1 11.1 4.8": ["electrify"], "9.0 4.3 0.5": ["soothes"], "-8.7 6.2 8.7": ["stevia"], "10.4 5.3 11.3": ["acrobat"], "2.8 8.1 1.7": ["skydivers"], "1.5 9.2 7.1": ["reconciles"], "12.8 11.6 4.9": ["turnstile"], "9.7 22.1 15.2": ["damsel"], "7.1 5.6 -1.2": ["tangential"], "-3.0 14.9 6.0": ["rucks"], "11.8 7.3 9.7": ["squawking"], "-7.7 9.4 4.5": ["ordain"], "4.1 9.6 10.3": ["recasting"], "-0.1 6.9 5.7": ["generalist"], "0.4 12.7 -2.4": ["construe"], "0.6 7.8 9.3": ["aborting"], "-2.2 5.3 7.0": ["modulated"], "14.9 4.8 10.6": ["spattered"], "1.5 -1.7 5.0": ["workbooks"], "3.7 2.3 23.8": ["listeria"], "5.3 5.1 5.8": ["purer"], "10.6 34.3 11.1": ["baddie"], "9.6 4.7 6.7": ["experimentally"], "14.5 2.7 8.7": ["screeched"], "17.9 7.1 13.0": ["amusements"], "0.6 2.9 7.0": ["annotation"], "2.9 25.2 4.0": ["barbarity"], "-8.1 6.3 0.6": ["ophthalmologists"], "6.8 5.5 43.3": ["humpbacks"], "-3.2 15.1 8.1": ["impetuous"], "6.0 9.5 16.5": ["baldness"], "13.2 15.4 15.6": ["biosphere"], "14.2 18.2 3.1": ["animating"], "6.7 3.3 22.4": ["tang"], "0.2 0.1 -2.7": ["spectroscopy"], "-3.9 4.4 3.4": ["preoccupations"], "10.6 11.6 6.6": ["masterstroke"], "14.3 6.9 1.0": ["volumetric"], "11.1 10.0 15.3": ["weedy"], "11.8 19.0 25.2": ["dandelions"], "2.7 10.1 5.6": ["halogen"], "-4.2 10.2 -0.4": ["unrecorded"], "-1.9 -1.9 19.4": ["simulcasting"], "3.9 5.1 4.6": ["fingering"], "11.3 10.7 10.1": ["circumnavigate"], "0.4 18.4 10.8": ["fogging"], "-7.9 22.8 9.8": ["sidearm"], "1.2 5.7 3.9": ["fiduciaries"], "0.4 4.7 1.7": ["trendsetters"], "8.6 18.2 13.4": ["emotionless"], "-7.6 -0.5 -0.2": ["breastfed"], "12.3 9.8 17.4": ["pi"], "3.9 13.6 13.6": ["preordained"], "7.4 12.9 11.3": ["nanosecond"], "5.8 1.2 5.7": ["erotica"], "3.9 0.9 2.7": ["electromechanical"], "0.7 5.8 9.8": ["bancassurance"], "8.1 5.3 13.0": ["eviscerated"], "5.5 1.5 4.8": ["lunched"], "-5.9 15.6 7.3": ["affective"], "-6.5 2.7 -6.1": ["tenable"], "6.3 1.2 9.7": ["knickknacks"], "-4.9 11.6 1.9": ["badgering"], "10.8 22.4 4.0": ["deniers"], "7.4 -3.4 2.2": ["chiming"], "7.5 9.0 6.3": ["expectedly"], "11.2 9.1 12.8": ["jpg"], "9.4 6.1 -0.1": ["enhancer"], "6.3 4.3 2.2": ["sterilizing"], "12.0 10.1 -0.3": ["painlessly"], "6.4 13.4 6.0": ["assail"], "18.6 10.9 15.7": ["igloo"], "9.3 22.2 6.8": ["searcher"], "7.6 3.8 17.1": ["cal"], "7.9 9.0 10.3": ["shyly", "vowel"], "-9.8 1.3 8.4": ["playwriting"], "-6.0 4.4 3.1": ["prognostic"], "-3.8 7.9 3.3": ["unheated"], "3.0 17.0 6.3": ["letdowns"], "4.7 0.5 9.8": ["paperboard"], "0.9 0.1 11.1": ["orchestrations"], "2.8 7.3 9.9": ["mumble"], "13.0 23.0 9.1": ["dislodging"], "-9.3 7.4 2.1": ["signer"], "4.0 11.6 1.3": ["beck"], "0.3 2.5 7.0": ["showbusiness"], "-1.3 2.9 10.1": ["logbook"], "-0.7 11.1 7.6": ["sunspots"], "15.4 14.4 35.9": ["robin"], "3.2 7.1 6.1": ["farmhouses"], "-5.6 12.6 2.7": ["deviates"], "4.0 9.6 10.1": ["discordant"], "10.4 22.8 9.4": ["callously"], "1.6 19.1 12.3": ["paramour"], "12.3 23.2 9.7": ["scoundrels"], "1.1 24.1 10.1": ["canard"], "2.5 14.2 11.5": ["enraging"], "-6.9 4.8 3.3": ["haredi"], "2.9 -0.2 3.8": ["segued"], "0.6 5.9 12.3": ["darkroom"], "-0.3 11.2 10.0": ["puritanical"], "-3.7 5.8 5.9": ["visioning"], "7.8 6.3 2.7": ["crosstown"], "15.0 10.1 16.6": ["penises"], "11.2 7.6 17.9": ["treehouse"], "2.3 7.8 12.7": ["headboard"], "-3.0 4.7 10.4": ["aqueduct"], "8.8 14.0 4.2": ["alacrity"], "21.6 20.3 7.0": ["baddest"], "9.2 19.9 6.6": ["smugly"], "2.6 -0.3 -1.6": ["dispels"], "0.4 5.0 13.1": ["taka"], "6.9 8.2 -0.2": ["pester"], "33.9 30.3 10.3": ["mightiest"], "8.3 -0.5 8.2": ["crocheted"], "3.1 8.2 9.7": ["moviemakers"], "1.3 18.8 2.7": ["claustrophobia"], "-5.3 7.2 2.8": ["overstep"], "-4.0 1.1 4.6": ["paracetamol"], "0.8 -0.3 9.7": ["quirkiness"], "4.0 2.4 8.9": ["professorial"], "15.7 3.9 -0.3": ["consolidator"], "3.2 15.9 8.7": ["ganged"], "1.8 14.9 7.7": ["lefts"], "11.6 0.7 5.0": ["pronto"], "7.7 8.3 2.5": ["cannoned"], "4.0 8.5 49.5": ["fisher"], "2.9 -0.1 35.0": ["ling"], "2.7 0.7 2.8": ["jockeyed"], "-0.5 29.3 3.0": ["worshiper"], "10.6 4.1 6.5": ["entices"], "7.8 -4.6 8.8": ["marring"], "3.3 13.7 10.7": ["fagot"], "3.9 18.0 23.9": ["canker"], "4.0 -1.4 7.2": ["castration"], "-1.3 10.2 4.2": ["distinctiveness"], "11.3 22.1 15.1": ["ramparts"], "-5.1 7.5 2.9": ["bebop"], "18.4 4.8 17.6": ["hued"], "-1.9 9.4 4.5": ["maudlin"], "17.4 3.8 16.3": ["chinese"], "7.0 8.5 24.0": ["eggshells"], "10.7 16.7 4.0": ["inwards"], "-0.6 10.8 22.4": ["cacao"], "2.5 11.2 11.5": ["airshow"], "-5.6 8.0 1.7": ["familiarization"], "1.1 12.2 9.1": ["pumper"], "11.6 0.2 4.3": ["chalets"], "4.0 1.9 12.5": ["telegenic"], "-2.0 0.7 7.1": ["champing"], "7.4 1.0 14.6": ["rhinestones"], "23.6 11.9 22.9": ["leprechaun"], "7.4 4.3 23.3": ["oceanography"], "10.1 -0.1 31.7": ["cannery"], "15.9 11.2 13.6": ["cacti"], "1.9 4.9 -3.4": ["certificated"], "2.0 10.2 8.4": ["suffrage"], "12.1 7.7 11.5": ["quangos"], "7.7 1.8 24.5": ["fryer"], "18.0 11.2 23.9": ["iridescent"], "-7.0 12.7 14.8": ["germination"], "7.9 8.3 4.6": ["presser"], "14.3 16.1 16.5": ["noggin"], "5.2 16.2 27.5": ["pansies"], "17.4 6.6 5.2": ["futurist"], "0.4 4.2 -1.3": ["neuro"], "2.6 5.5 9.8": ["hedonism"], "-6.1 7.5 1.7": ["conduction"], "10.4 15.6 6.8": ["banality"], "17.5 1.6 13.1": ["gluing"], "10.4 15.8 6.5": ["underachiever"], "4.1 1.2 12.1": ["weightlifter"], "8.0 2.6 6.8": ["prefab"], "16.7 21.6 -0.0": ["allying"], "15.1 9.5 20.6": ["kudzu"], "2.5 18.0 8.0": ["overflights"], "-4.5 17.0 -1.9": ["slandered"], "-6.1 -0.4 13.9": ["provincially"], "9.6 1.7 13.5": ["ti"], "2.9 20.0 7.6": ["nihilism"], "2.1 10.8 3.9": ["descendent"], "-1.7 11.9 -2.5": ["recharges"], "13.2 30.2 10.2": ["lackeys"], "8.5 5.6 4.8": ["postscript"], "2.8 6.3 31.2": ["antler"], "5.0 5.5 10.2": ["bemusement"], "-6.0 20.2 9.7": ["gunplay"], "-2.2 21.1 8.3": ["dacoits"], "-4.9 10.8 -5.9": ["saddening"], "4.6 2.0 6.2": ["groused"], "8.0 9.4 5.7": ["fables"], "8.9 0.1 6.7": ["accessorized"], "13.9 33.0 11.8": ["implacable"], "3.8 8.0 1.4": ["thousandths"], "1.8 5.1 5.6": ["warded"], "10.6 2.9 6.0": ["mags"], "13.1 10.3 13.4": ["doggone"], "11.2 7.0 4.5": ["unnerve"], "6.2 6.3 -0.3": ["westernmost"], "0.5 24.1 12.1": ["houseguests"], "-5.1 -0.5 13.5": ["wakeboarding"], "2.9 2.5 5.9": ["oversupplied"], "11.8 6.8 2.9": ["hippest"], "6.6 3.8 4.3": ["rethought"], "5.0 13.5 12.1": ["effeminate"], "4.0 11.6 9.4": ["tryline"], "-2.8 -3.9 9.2": ["archdiocesan"], "7.8 8.4 18.7": ["pyrotechnic"], "9.9 13.8 14.6": ["hibernating"], "13.4 -6.5 2.6": ["rehear"], "-0.3 6.3 5.0": ["scoped"], "2.9 9.3 -0.9": ["dampers"], "4.0 -0.0 2.4": ["horoscopes"], "11.8 4.5 6.4": ["redux", "sats"], "4.9 5.2 1.2": ["typeface"], "23.6 14.2 10.6": ["pitchforks"], "1.3 8.5 13.5": ["sunroom"], "14.6 7.3 17.6": ["necked"], "6.1 7.1 23.3": ["autumnal"], "2.2 5.3 23.2": ["edibles"], "6.4 2.7 7.5": ["reengineering"], "-0.3 17.7 8.4": ["unjustifiably"], "5.4 10.9 40.6": ["sunfish"], "-2.3 2.7 0.1": ["sobered"], "1.9 16.6 0.7": ["obliquely"], "7.1 8.1 4.7": ["wavers"], "10.6 6.9 9.3": ["strongmen"], "5.5 8.0 4.5": ["swig"], "6.5 11.2 6.5": ["irksome"], "2.5 13.5 2.9": ["earshot"], "3.2 2.6 10.9": ["archbishops"], "17.6 12.2 9.0": ["squirting"], "16.8 7.5 13.6": ["unloads"], "-11.8 -7.1 4.1": ["ineligibility"], "-11.0 8.3 1.8": ["mixtapes"], "7.7 7.4 6.8": ["hardcourts"], "8.9 12.6 7.5": ["wacko"], "5.4 22.7 12.2": ["nigger"], "8.5 22.5 6.7": ["besieging"], "-4.6 32.4 6.4": ["deserter"], "-0.7 5.9 -2.1": ["frisking"], "9.3 16.0 10.7": ["quartered"], "11.0 6.2 4.4": ["squeaks"], "6.5 5.2 3.5": ["internals"], "11.4 26.4 6.6": ["colonialists"], "1.3 9.1 6.6": ["filer"], "-14.5 0.3 2.6": ["occupancies"], "0.8 1.8 -0.9": ["uncompleted"], "-4.8 6.3 3.7": ["neuropathy"], "10.6 3.6 7.6": ["fastening"], "8.0 10.5 0.6": ["whitewashing"], "6.8 10.2 1.5": ["inoffensive"], "-1.1 5.1 5.7": ["spirituals"], "3.1 4.5 2.7": ["gasket"], "3.4 4.3 9.9": ["mas"], "5.1 13.4 9.6": ["procrastinators"], "4.8 14.9 11.1": ["navigators"], "16.2 7.0 8.8": ["clamber"], "6.8 17.3 11.3": ["ungovernable"], "5.7 -5.2 13.2": ["snipped"], "3.7 8.0 10.6": ["attenuated"], "1.7 8.4 7.8": ["sparkplug"], "3.0 15.4 5.6": ["intrudes"], "3.6 4.2 5.9": ["biomechanics"], "-2.1 8.1 0.7": ["exercisers"], "4.6 3.5 5.7": ["li"], "-0.1 12.2 -1.3": ["pursuance"], "2.5 5.8 6.7": ["blooped"], "13.9 7.1 27.4": ["skimmer"], "8.3 6.0 1.1": ["shellshocked"], "-5.1 0.8 23.8": ["quinoa"], "12.3 22.2 10.1": ["sissy"], "5.8 10.0 5.1": ["convection"], "7.7 3.1 0.3": ["kindled"], "-5.5 6.0 12.6": ["dewatering"], "-1.2 4.5 5.8": ["synthetics"], "-7.2 14.2 13.0": ["fencers"], "1.8 0.7 -0.9": ["ambassadorial"], "6.9 17.0 11.1": ["equanimity"], "9.8 15.4 8.2": ["stupidest"], "13.2 2.9 23.5": ["redwoods"], "4.1 13.3 4.9": ["redefinition"], "13.1 17.6 8.0": ["staunchest"], "9.8 12.1 9.0": ["snicker"], "-1.8 -3.7 14.5": ["slopestyle"], "15.0 -1.6 18.2": ["flecked"], "0.2 8.5 1.6": ["soundbites"], "11.1 8.2 14.2": ["standbys"], "9.7 23.0 8.1": ["teleport"], "2.6 7.9 1.8": ["actuator"], "5.5 6.7 11.2": ["baggie"], "-0.2 5.0 5.7": ["docents"], "3.4 -0.6 1.3": ["webisodes"], "12.8 -0.3 11.9": ["os"], "2.8 3.3 21.3": ["prefectural"], "11.0 5.7 12.5": ["winched"], "-2.1 11.8 16.2": ["timberlands"], "6.5 24.5 15.5": ["copter"], "-1.7 12.9 8.2": ["evocation"], "2.0 0.8 12.0": ["layin"], "19.5 11.5 14.6": ["rectangles"], "12.1 6.6 29.9": ["cypress"], "-6.5 -0.5 8.4": ["paraprofessionals"], "9.9 9.4 5.7": ["weds"], "6.7 -2.2 1.6": ["whetted"], "-3.2 -0.6 7.8": ["reinserted"], "6.8 20.4 1.1": ["salvos"], "5.7 5.7 53.9": ["bluefin"], "6.5 3.5 28.6": ["plumage"], "16.6 13.7 25.3": ["inedible"], "9.9 7.0 2.9": ["reverberates"], "6.6 11.3 13.9": ["baselines"], "-3.0 25.8 7.0": ["rearm"], "-0.9 7.4 12.4": ["boron"], "13.0 9.4 38.7": ["meatball"], "8.1 5.0 15.1": ["frilly"], "2.7 -3.0 -3.0": ["wrangles"], "14.4 7.6 13.0": ["gent"], "3.0 0.1 6.7": ["fleshing"], "8.5 2.1 7.1": ["lunching"], "2.2 5.2 53.7": ["whitefish"], "13.7 4.8 46.3": ["sardine"], "10.4 -1.1 9.4": ["subsisting"], "3.2 10.6 3.3": ["sleeplessness"], "2.2 3.0 22.4": ["bologna"], "-1.1 7.8 30.5": ["chutney"], "4.6 7.8 9.3": ["cheetahs"], "2.2 17.0 9.9": ["foreplay"], "6.2 5.2 5.0": ["groundsman"], "6.5 11.4 8.7": ["comin"], "10.0 4.3 14.8": ["sarcophagus"], "11.0 11.9 35.8": ["iguanas"], "6.9 6.0 13.2": ["powdery"], "13.3 9.6 2.5": ["banishing"], "21.9 10.2 16.1": ["gnarled"], "3.7 0.1 5.3": ["merchantability"], "-5.8 21.0 4.5": ["noncombat"], "3.9 8.7 5.3": ["ipod"], "13.4 4.1 13.8": ["cellophane"], "5.4 -3.6 5.1": ["petabytes"], "7.7 3.7 18.0": ["palettes"], "3.9 8.7 9.7": ["depressingly"], "7.5 8.8 4.8": ["barmaid"], "10.5 -2.9 16.9": ["lustrous"], "-3.0 10.9 7.9": ["stopovers"], "6.7 1.2 0.3": ["disallowing"], "11.4 1.9 9.0": ["knotty"], "3.7 7.5 4.4": ["coalescing"], "3.1 -5.8 6.5": ["fasted"], "7.8 -1.7 3.6": ["reconsiders"], "18.1 8.3 22.6": ["pail"], "1.1 13.8 4.8": ["braver"], "1.1 5.6 -1.1": ["myspace"], "7.3 15.4 9.1": ["grimaces"], "21.7 17.9 34.3": ["grasshopper"], "9.3 19.6 9.4": ["stony"], "11.5 14.7 11.3": ["sicken"], "7.8 15.7 7.0": ["stonewall"], "16.1 13.7 19.3": ["appendages"], "6.7 1.7 2.0": ["invalidating"], "-2.8 1.7 4.6": ["thundershowers"], "2.9 -0.8 5.2": ["reconstructions"], "13.7 13.4 3.4": ["outrunning"], "11.5 9.9 4.2": ["bluetooth"], "6.4 19.0 -3.6": ["deciphered"], "-1.2 -1.9 -1.0": ["transcribe"], "-4.1 6.8 8.2": ["catchments", "defensibility", "parle"], "9.3 2.4 -5.2": ["twinned"], "2.7 4.0 5.2": ["yellowcake"], "-0.5 5.9 3.4": ["forgivable"], "4.6 7.8 11.1": ["waterproofing"], "5.9 7.3 2.5": ["overestimating"], "17.0 7.6 3.5": ["swiftness"], "3.0 2.2 10.3": ["streetlight"], "8.5 9.7 11.1": ["sunburned"], "5.3 8.3 7.6": ["doorknob"], "3.2 19.3 7.6": ["creeds"], "-10.1 5.4 13.7": ["lumpectomy"], "8.9 10.0 2.8": ["firebomb"], "8.8 7.1 11.8": ["surfs"], "4.9 6.2 7.4": ["workarounds"], "0.5 2.0 17.4": ["midwinter"], "0.3 4.1 3.5": ["syndromes"], "14.3 11.7 4.7": ["playthings"], "2.1 11.2 10.3": ["resettling"], "13.7 -4.0 0.7": ["countersued"], "11.1 9.2 10.0": ["altars"], "0.1 -0.6 5.7": ["squabbled"], "2.4 -7.5 3.1": ["symposiums"], "15.6 10.0 10.1": ["cheekily"], "10.3 12.2 5.0": ["flickers"], "11.6 13.3 7.9": ["eraser"], "15.0 21.3 5.2": ["interstellar"], "8.5 0.4 7.8": ["linings"], "-0.9 6.8 6.2": ["radium"], "2.6 -2.4 11.3": ["mariachi"], "5.9 9.5 10.3": ["preys"], "13.7 11.7 14.6": ["bam"], "4.1 -0.4 6.9": ["chanteuse"], "18.2 3.9 -1.6": ["oilman"], "7.3 9.6 10.3": ["cinderblock"], "11.6 -0.8 7.9": ["extravagantly"], "8.7 4.8 8.6": ["geneticists"], "5.9 11.4 7.4": ["unforeseeable"], "8.0 16.7 20.8": ["roosting"], "-3.9 1.8 10.1": ["lateness"], "14.8 16.3 8.2": ["peeing"], "-1.9 14.1 2.1": ["attenuation"], "5.9 8.2 4.6": ["niggle"], "5.0 14.1 10.8": ["catchphrases"], "-1.7 1.1 1.8": ["nevirapine"], "-0.2 5.1 2.3": ["illegible"], "-5.5 9.0 -4.5": ["ventilate"], "0.3 6.4 8.8": ["tickles"], "5.9 1.6 1.9": ["ville"], "-0.9 12.7 6.0": ["ff"], "7.9 2.9 12.2": ["bookmaking"], "9.9 15.7 34.5": ["carnivore"], "10.0 7.5 5.8": ["talismanic"], "2.8 16.1 -2.1": ["unfailing"], "3.0 7.3 8.0": ["polyphenols"], "16.8 14.6 6.0": ["yahoo"], "6.4 8.6 -2.2": ["permeable"], "5.0 -1.5 9.1": ["storytime"], "16.0 17.3 5.5": ["derisively"], "-0.5 18.1 12.4": ["stoicism"], "1.0 9.1 4.1": ["nightstand"], "14.3 15.6 7.9": ["swiveling"], "-0.2 2.7 5.1": ["multivitamins"], "-5.4 6.5 -1.6": ["pedagogical"], "7.9 18.1 4.2": ["ascends"], "4.1 7.8 4.4": ["spellings"], "2.1 6.9 23.6": ["jus"], "1.0 31.7 5.4": ["unwinnable"], "3.3 5.9 1.1": ["housebuilder"], "-0.2 11.9 7.2": ["egregiously"], "-4.0 0.3 10.0": ["gpt"], "-3.5 9.2 6.5": ["rubella"], "-0.7 8.4 3.6": ["taxiways"], "5.5 3.8 4.4": ["plies"], "-0.1 13.3 8.2": ["snide"], "3.8 -0.4 0.4": ["repurpose"], "15.5 4.0 5.5": ["gawking"], "-8.6 8.0 3.3": ["tehsil"], "-6.3 11.0 0.4": ["detainment"], "-3.6 2.3 11.7": ["distilleries"], "16.1 6.1 13.9": ["scoffing"], "1.1 2.5 0.1": ["washable"], "4.8 9.1 13.2": ["mercantile"], "2.6 4.3 -1.2": ["extranet"], "-5.5 3.0 -7.4": ["transfered"], "1.5 -3.7 -0.4": ["resells"], "1.9 6.2 -0.0": ["authenticating"], "16.5 6.0 22.3": ["daisy"], "2.5 4.7 11.6": ["gashes"], "0.1 6.7 37.9": ["kiwifruit"], "18.5 8.4 3.4": ["tsar"], "12.3 9.0 10.8": ["ouch"], "-2.3 19.0 11.8": ["southpaws"], "1.3 18.3 13.4": ["untouchables"], "4.4 -3.5 0.9": ["trendsetting"], "8.1 14.6 8.4": ["perceptual"], "5.6 7.3 3.5": ["costings"], "-4.5 3.7 1.3": ["advices"], "19.7 10.4 9.4": ["clambering"], "11.7 9.2 8.6": ["derisory"], "11.0 4.3 12.2": ["fabricator"], "3.0 1.3 3.1": ["verges"], "20.5 14.7 10.6": ["grandly"], "4.3 6.3 0.5": ["wick"], "-2.4 29.2 18.4": ["shipmates"], "8.2 4.4 14.2": ["sizzles"], "-0.3 11.0 -5.2": ["evangelistic"], "11.6 3.9 8.1": ["winsome"], "9.3 3.4 8.6": ["tantalizingly"], "20.4 10.1 8.3": ["shuddering"], "1.5 23.7 6.0": ["communalism"], "12.6 6.7 21.8": ["shuffleboard"], "21.7 6.9 5.3": ["gazillion"], "4.8 12.7 1.6": ["reenter"], "0.4 3.7 23.7": ["masala"], "11.6 6.0 8.2": ["illusionist"], "6.6 1.2 6.7": ["midlands"], "2.2 18.5 16.0": ["euphemisms"], "7.6 5.8 9.3": ["nonrecurring"], "-0.5 7.4 1.1": ["miscarried"], "3.2 3.9 7.3": ["sunday"], "16.1 2.3 8.3": ["rubberized"], "0.9 10.8 2.0": ["antagonized"], "10.9 13.5 7.1": ["shackle"], "-4.0 -2.8 10.2": ["grammes"], "11.8 8.1 1.9": ["charlatans"], "4.3 13.1 10.9": ["grope"], "10.9 6.4 28.1": ["breadcrumbs"], "7.5 6.1 9.0": ["gearboxes"], "10.8 15.5 -2.0": ["magnifying"], "-3.6 1.6 7.8": ["backplane"], "-0.4 6.4 13.6": ["downhills"], "18.6 -3.6 14.9": ["creme"], "4.5 2.3 14.1": ["ticketholders"], "10.6 1.6 19.3": ["jeweled"], "3.1 9.3 15.7": ["tailpipe"], "3.5 -1.2 5.7": ["couplings"], "-0.2 3.5 6.7": ["alleviation"], "7.6 15.1 1.0": ["defiled"], "15.7 -1.2 0.9": ["hogged"], "13.8 0.9 9.3": ["snafus"], "-4.1 5.4 3.1": ["ischemic"], "7.2 -6.5 14.9": ["healthily"], "-2.1 10.0 18.7": ["pomegranates"], "0.9 5.8 6.2": ["rotavirus"], "4.7 3.0 14.3": ["kindergarteners"], "3.8 9.3 5.9": ["accrues"], "15.7 8.9 5.1": ["dealmaker"], "0.5 15.0 7.7": ["nitpicking"], "4.2 2.9 10.3": ["scrounging"], "-9.8 2.4 4.0": ["quartets"], "6.3 1.4 31.9": ["yams"], "-7.8 15.1 6.2": ["insureds"], "16.8 8.4 7.3": ["clattering"], "15.1 5.9 7.3": ["lawnmowers"], "11.9 5.3 7.9": ["interconnecting"], "5.6 6.3 6.9": ["actives"], "1.7 9.3 7.0": ["litigators"], "0.2 2.1 13.3": ["touristy"], "6.4 10.7 3.8": ["firebombed"], "16.9 0.8 16.1": ["bronzed"], "-2.7 -2.9 1.4": ["sm"], "-6.5 8.8 -5.5": ["equivocal"], "-3.1 12.6 1.8": ["impedance"], "-0.5 -0.7 10.8": ["dietitians"], "-10.4 3.6 13.7": ["liquors"], "-2.8 0.8 2.0": ["invoiced"], "15.3 14.2 35.7": ["iguana"], "6.2 7.5 5.9": ["pervading"], "16.1 4.9 11.8": ["cratered"], "1.8 7.7 3.4": ["interchangeably"], "6.1 -1.4 13.6": ["bookended"], "5.9 4.1 8.2": ["approximated"], "3.2 10.7 7.3": ["whines"], "8.1 5.0 31.3": ["slaw"], "-0.2 12.1 5.2": ["frontbench"], "13.2 15.9 24.3": ["mallet"], "16.1 6.6 12.3": ["gnawed"], "-3.5 14.9 -0.9": ["untraceable"], "9.7 0.8 -0.4": ["pervasiveness"], "3.6 12.0 6.1": ["inflexibility"], "4.2 8.9 12.1": ["aeration"], "3.5 11.1 15.5": ["extinctions"], "1.3 8.3 3.8": ["scolds"], "9.7 9.0 14.0": ["dooming"], "1.7 5.2 7.5": ["retrenchments"], "9.5 0.3 10.4": ["ringers"], "2.0 10.9 5.7": ["masterly"], "11.4 24.5 -1.4": ["ambushing"], "4.8 29.8 3.6": ["oppressing"], "3.5 0.7 5.9": ["conservators"], "9.3 1.7 9.5": ["fer"], "9.0 0.2 31.4": ["yam"], "5.5 3.6 18.0": ["steamboat"], "16.9 7.2 12.6": ["noisemakers"], "-7.0 5.7 9.8": ["moisturizing"], "-1.0 3.2 6.8": ["recurred"], "12.1 11.2 0.3": ["nomad"], "4.7 -1.6 0.9": ["globetrotting"], "9.1 8.8 4.9": ["interconnectedness"], "-1.9 3.8 -2.0": ["underpasses"], "1.3 1.9 5.1": ["lactose"], "4.8 5.3 5.5": ["simvastatin"], "-4.1 1.0 14.7": ["geldings"], "19.7 9.7 12.8": ["splayed"], "0.4 10.5 3.5": ["plausibility"], "3.0 15.3 -0.9": ["fomented"], "13.2 8.2 -0.8": ["byword"], "11.9 12.8 3.6": ["hissed"], "1.5 22.3 12.3": ["patriarchy"], "20.0 5.1 7.1": ["squashing"], "2.6 9.8 9.5": ["tranquilizers"], "6.2 6.8 9.3": ["rasping"], "19.2 14.6 7.2": ["whoosh"], "10.7 6.8 7.2": ["dims"], "6.4 13.8 11.7": ["burqas"], "1.0 -1.0 17.6": ["tresses"], "9.9 1.6 6.1": ["encyclopedias"], "9.8 2.3 13.3": ["heavyset"], "3.4 21.2 14.6": ["taggers"], "9.9 7.0 0.9": ["crowdsourcing"], "4.3 1.4 3.9": ["debunks"], "8.0 11.2 4.7": ["sprayer"], "10.8 7.3 38.0": ["paella"], "1.6 -0.3 1.5": ["archivists"], "13.5 17.7 17.9": ["phishers"], "1.1 7.9 -0.9": ["oversights"], "10.6 3.9 12.1": ["intriguingly"], "6.7 7.3 15.7": ["tambourine"], "8.9 -0.3 25.0": ["tarts"], "-6.6 3.9 2.6": ["clerked"], "10.9 9.7 11.0": ["toolbars"], "12.4 0.3 4.1": ["fiddles"], "12.0 15.8 5.7": ["eastwards"], "7.3 14.9 3.5": ["incredulously"], "11.5 7.2 17.0": ["linoleum"], "-4.8 10.7 -2.1": ["chargeable"], "6.6 2.8 8.5": ["floss"], "8.7 13.9 4.6": ["warping"], "20.0 21.4 6.5": ["cloaking"], "4.7 14.6 12.1": ["headbutt"], "4.3 11.7 2.3": ["injector"], "-2.2 9.4 2.4": ["conscientiously"], "14.2 9.1 -2.2": ["blare"], "11.2 10.8 18.8": ["trellis"], "-2.1 4.0 13.9": ["roofers"], "5.1 2.1 3.7": ["hipper"], "2.9 3.6 2.7": ["crocheting"], "11.6 16.1 8.7": ["overrunning"], "1.1 30.6 7.4": ["turncoat"], "5.4 9.2 19.2": ["panthers"], "9.4 13.2 2.0": ["derisive"], "19.2 11.1 5.0": ["pusher"], "1.7 -0.7 17.1": ["birdhouses"], "10.6 7.9 2.6": ["jinxed"], "12.7 4.7 11.7": ["rad"], "7.8 10.9 6.5": ["sniffles"], "-5.2 18.9 0.7": ["distrusted"], "-3.4 8.9 10.7": ["homeroom"], "0.8 20.9 2.9": ["airstrips"], "1.8 28.7 12.0": ["subjugated"], "12.5 12.6 10.4": ["sunlit"], "9.5 3.4 10.6": ["limber"], "1.9 1.4 1.1": ["callable"], "-1.3 -2.4 6.7": ["snowboards"], "-4.7 13.4 3.9": ["realignments"], "-12.2 4.8 6.1": ["diuretics"], "-6.0 13.0 9.2": ["costars"], "6.6 11.6 10.2": ["heaviness"], "3.6 5.3 7.2": ["colliery"], "2.4 11.2 16.5": ["coloration"], "3.9 3.2 6.0": ["tussling"], "10.3 13.8 13.5": ["divot"], "0.8 22.1 7.9": ["solders"], "19.2 4.3 -0.9": ["flickered"], "-4.1 -0.2 -2.4": ["rapporteur"], "11.1 1.6 11.3": ["ringmaster"], "8.7 7.0 5.4": ["scavenged"], "2.4 -0.8 9.1": ["tassels"], "3.1 26.6 11.8": ["unprincipled"], "13.2 5.9 11.0": ["ennui"], "3.8 4.3 2.9": ["processional"], "9.2 0.3 4.5": ["ou"], "1.2 8.0 11.4": ["upgrader"], "-0.1 3.6 5.3": ["visitations"], "25.0 -0.1 1.1": ["billon"], "10.4 9.0 5.4": ["launchpad"], "3.9 -3.2 21.3": ["samplings"], "-7.2 16.8 6.5": ["slights"], "4.3 9.2 2.4": ["porosity"], "16.3 15.6 8.7": ["sickle"], "-3.7 0.3 1.6": ["immunogenicity"], "15.5 8.1 1.2": ["buzzes"], "-1.5 13.6 5.9": ["graciousness"], "6.3 10.3 0.3": ["rebooted"], "7.9 -0.7 21.4": ["dachshund"], "-1.1 11.9 10.1": ["lifes"], "-0.7 1.8 8.5": ["epigenetic"], "0.2 20.0 0.3": ["doer"], "16.6 12.7 10.9": ["dregs"], "22.9 10.8 15.0": ["robo"], "3.9 11.8 16.9": ["berthed"], "-9.7 4.6 3.8": ["neutropenia"], "2.5 15.2 11.6": ["consort"], "11.9 17.1 16.9": ["starlings"], "-0.9 17.1 8.6": ["victimhood"], "5.2 6.2 0.0": ["runaround"], "-0.4 -1.7 8.4": ["multivitamin"], "4.0 4.2 5.5": ["sonogram"], "7.3 6.8 2.3": ["keypads"], "-1.7 3.9 -0.8": ["eloped"], "6.1 3.0 5.4": ["phonebook"], "-4.9 -5.2 -1.0": ["accreditations"], "6.7 8.9 0.9": ["saturating"], "1.2 17.7 6.0": ["abet"], "-2.5 -0.9 -1.2": ["excreted"], "-1.2 16.9 -3.6": ["genocides"], "-8.8 0.1 14.4": ["jean"], "3.1 8.3 9.8": ["amyloid"], "-4.1 4.8 7.1": ["thespians"], "8.0 11.9 21.2": ["slipper"], "6.3 12.6 23.5": ["spinnerbaits"], "11.2 14.3 3.0": ["airlifting"], "9.3 21.8 10.5": ["immobilize"], "8.9 0.9 2.0": ["keychain"], "12.3 4.8 16.0": ["fibrous"], "4.0 2.9 5.2": ["tweeters"], "16.0 31.7 7.1": ["invulnerable"], "-1.9 6.6 18.8": ["marinate"], "4.6 10.1 5.7": ["collude", "boere"], "-0.5 1.3 7.8": ["sesquicentennial"], "4.3 15.4 11.6": ["nonchalance"], "10.3 7.5 6.0": ["cooing"], "9.7 8.1 -4.2": ["transportable"], "5.9 0.7 9.1": ["neckties"], "-7.1 8.3 0.6": ["stater"], "5.3 -0.2 9.5": ["minis"], "12.9 12.7 19.1": ["pingpong"], "1.4 12.6 24.8": ["berthing"], "7.5 0.2 15.2": ["subcontracts"], "6.5 14.9 9.9": ["enchantment"], "5.4 0.4 8.0": ["spindles"], "-0.7 12.0 7.4": ["expectancy"], "0.5 6.5 5.7": ["encyclical"], "4.7 9.5 -0.6": ["annexes"], "-1.6 6.6 0.5": ["discourses"], "-1.6 16.4 7.0": ["disadvantageous"], "13.9 7.2 11.5": ["boatloads"], "0.4 11.3 -1.8": ["concretely"], "13.5 10.6 11.0": ["puppeteers"], "3.6 14.6 4.6": ["lister"], "-9.0 1.9 5.8": ["discography"], "5.6 19.6 26.1": ["nymphs"], "-1.9 9.1 9.3": ["geocaching"], "5.7 8.6 1.0": ["sensationalist"], "18.2 6.5 17.6": ["gorging"], "-4.3 21.2 4.7": ["pretexts"], "10.4 27.8 5.2": ["napalm"], "-8.6 1.7 25.9": ["salvia"], "21.2 28.0 9.3": ["beastly"], "-3.7 -0.9 8.6": ["megabit"], "3.1 3.8 -5.1": ["monetized"], "0.0 7.3 7.5": ["bossed"], "-0.4 9.6 9.4": ["depresses"], "14.0 1.9 26.4": ["flamingos"], "10.1 2.1 1.0": ["scrolled"], "-1.3 9.8 11.1": ["preselection"], "-0.2 10.8 8.6": ["disreputable"], "6.0 1.5 8.7": ["incubate"], "10.0 11.0 32.8": ["flipper"], "5.7 16.5 2.3": ["geolocation"], "10.5 2.6 3.1": ["etcetera"], "12.2 0.8 9.5": ["cu"], "-2.7 3.1 8.5": ["granularity"], "-0.6 7.3 3.6": ["posit"], "6.0 12.8 3.0": ["skydiver"], "-9.1 12.1 4.4": ["quotable"], "5.0 14.7 7.9": ["filibustering"], "5.3 3.2 6.5": ["saunas"], "4.4 16.4 11.0": ["providence"], "7.9 2.6 -4.0": ["interconnectivity"], "5.5 4.5 3.9": ["cantons"], "0.6 6.6 1.1": ["acclimatise"], "12.9 11.8 11.2": ["tingle"], "-3.4 4.8 14.9": ["survivorship"], "-4.5 17.0 0.4": ["stigmatization"], "16.0 11.6 13.1": ["quack"], "16.1 11.3 19.8": ["baboon"], "10.3 12.4 -0.1": ["gossips"], "7.2 3.8 12.3": ["snowbank"], "-5.1 -1.4 8.8": ["harpsichord"], "6.1 8.0 9.5": ["secondaries"], "13.5 5.6 6.5": ["presage", "couponer"], "25.6 10.2 13.9": ["hulk"], "-10.7 -9.7 2.8": ["aftercare"], "0.3 11.2 -1.1": ["evangelize"], "14.7 5.4 9.3": ["hypnotist"], "5.2 12.7 9.3": ["goalkicking"], "9.9 2.1 -1.6": ["sodomizing"], "7.8 3.8 8.8": ["buffed"], "-5.1 -0.7 2.5": ["preeclampsia"], "-6.5 -3.1 1.1": ["deputizing"], "3.4 9.4 23.1": ["softwood"], "12.5 25.5 3.9": ["lackey"], "11.6 4.8 31.8": ["spuds"], "8.8 7.8 6.4": ["astrological"], "17.6 5.6 0.1": ["shockwaves"], "5.0 12.9 17.4": ["pitbull"], "7.5 5.3 13.0": ["bladed"], "14.1 4.9 10.0": ["incubating"], "-0.7 9.2 3.0": ["believability"], "-4.1 5.8 6.3": ["gastroenterologist"], "18.9 6.7 10.9": ["statuesque"], "-2.6 11.8 9.5": ["neurotransmitter"], "12.7 7.4 2.7": ["lampooning"], "4.1 11.0 5.7": ["raiser"], "-5.2 10.0 15.1": ["hypoxia"], "7.8 3.9 18.0": ["splice"], "7.5 7.1 -0.1": ["fireproof"], "10.8 7.6 10.2": ["bricked"], "15.5 8.8 13.7": ["shrivel"], "-5.0 18.5 9.3": ["demining"], "2.6 3.1 14.5": ["scrubber"], "-2.8 3.9 6.2": ["spg"], "3.5 8.3 12.1": ["umps"], "-3.7 27.0 7.9": ["betrayals"], "4.3 -3.7 8.7": ["allots"], "12.7 -0.0 8.5": ["doodles"], "8.0 5.5 15.1": ["engravings"], "2.5 7.6 14.5": ["crispness"], "-7.3 5.1 6.1": ["maximums"], "5.4 10.8 -0.6": ["repentant"], "-2.1 17.2 10.7": ["uninvolved"], "12.0 8.5 1.6": ["trailblazers"], "5.0 0.6 12.2": ["reattached"], "2.2 8.9 23.5": ["tsp"], "3.7 9.9 12.3": ["mulligan"], "-4.6 9.1 5.3": ["decompress"], "4.3 1.2 4.3": ["mangers"], "3.0 17.3 7.2": ["desensitized"], "0.1 9.7 3.6": ["backfoot"], "2.1 3.4 5.7": ["markups"], "8.0 5.8 5.1": ["hesitantly"], "5.7 8.4 6.9": ["steels"], "-15.9 2.6 6.8": ["corticosteroids"], "3.6 30.3 2.6": ["aggressions"], "27.0 23.4 8.9": ["fiend"], "-1.3 13.9 3.0": ["playbooks"], "5.5 15.1 9.4": ["reverie"], "6.0 10.5 9.1": ["mildest"], "4.7 10.8 12.7": ["speller"], "9.3 -1.0 23.3": ["taxidermy"], "6.4 6.2 1.5": ["doze"], "18.5 14.5 11.1": ["engulfs"], "-2.2 4.6 12.6": ["dressers"], "0.0 -0.3 5.3": ["chalks"], "8.5 9.4 10.5": ["sounder"], "-7.4 6.1 4.7": ["toxicities"], "0.2 7.9 4.8": ["ovations"], "0.6 12.3 -2.7": ["implores"], "13.9 -5.2 0.6": ["hawked"], "9.3 21.3 3.8": ["psychopaths"], "4.8 5.7 50.9": ["whiting"], "3.3 4.6 4.7": ["roofline"], "8.7 5.9 13.1": ["ridiculousness"], "-1.2 13.7 -2.8": ["evenhanded"], "1.4 7.0 9.3": ["mouthy"], "-1.6 2.7 5.9": ["paraprofessional"], "6.7 12.5 2.9": ["powerlines"], "16.4 13.1 9.7": ["impatiently"], "-6.6 15.6 5.8": ["photojournalists"], "15.6 9.4 19.8": ["fishbowl"], "3.1 20.1 4.3": ["hindrances"], "1.2 4.8 4.2": ["nt"], "11.7 9.5 3.1": ["thumps"], "6.2 5.8 12.6": ["knotting"], "16.0 10.2 11.6": ["boneheaded"], "-0.5 0.5 5.2": ["decoders"], "14.0 5.2 6.1": ["parlous"], "5.7 4.4 5.6": ["whit", "servicio"], "2.3 1.3 19.1": ["undercooked"], "-2.5 3.5 12.7": ["chafe"], "-5.7 7.0 3.5": ["interject"], "8.1 4.3 6.2": ["european"], "-2.7 0.3 4.4": ["cufflinks"], "10.6 6.0 8.4": ["dominatrix"], "4.9 17.0 4.6": ["tropes"], "9.0 12.3 0.8": ["doesn"], "9.7 15.6 0.8": ["hypersensitive"], "-12.1 13.6 5.8": ["debater"], "0.8 -1.1 2.2": ["furnishes"], "17.7 2.6 9.0": ["flexes"], "-0.5 7.0 2.7": ["immunological"], "5.8 6.9 5.4": ["bagpipe"], "2.0 -4.7 5.3": ["rhp"], "3.0 8.7 11.5": ["macros", "interlaced"], "13.8 9.6 7.2": ["eminence"], "0.9 7.2 2.3": ["imbue"], "2.8 11.9 7.1": ["deleterious"], "3.7 6.8 31.3": ["sealers"], "-1.6 4.9 12.5": ["matt"], "-3.2 8.5 16.9": ["exacta"], "3.2 12.3 10.3": ["windowsill"], "-1.8 3.8 7.9": ["cathode"], "1.4 -0.7 15.0": ["botox"], "5.2 6.8 3.5": ["thence"], "4.8 9.4 4.6": ["payola"], "-4.7 10.1 14.3": ["breadwinners"], "3.5 4.9 1.8": ["unenthusiastic"], "6.9 13.1 10.2": ["jealously"], "5.4 0.5 16.6": ["delis"], "5.4 5.2 -2.9": ["expels"], "15.8 16.2 9.3": ["stiffly"], "0.9 17.9 -3.7": ["uncritical"], "14.5 4.7 14.3": ["windfarm"], "9.7 2.1 20.6": ["pontoons"], "3.4 3.6 10.3": ["trouser"], "2.5 15.1 2.6": ["burka"], "-11.6 8.1 2.6": ["prescribers"], "5.2 -0.7 4.4": ["muggings"], "26.4 5.7 5.6": ["firmament"], "11.4 13.8 12.4": ["ugh"], "11.6 7.8 10.4": ["mothball"], "7.7 12.3 6.4": ["chinks"], "1.9 0.2 4.6": ["reflux"], "2.1 16.8 7.4": ["easterly"], "1.0 8.3 6.4": ["outliers"], "3.5 8.8 11.6": ["approvingly"], "13.2 6.5 5.8": ["refitted"], "9.1 3.1 -6.1": ["leaseback"], "14.4 13.2 34.9": ["salamander"], "9.7 2.7 10.8": ["christmas"], "4.1 9.9 3.4": ["acoustically"], "14.7 19.0 8.6": ["prostrate"], "3.7 9.8 3.3": ["unsuited"], "-2.3 7.3 18.2": ["pasteurized"], "8.9 22.6 7.2": ["superbugs"], "1.5 -0.2 3.3": ["asap"], "6.4 0.8 5.4": ["changeovers"], "0.5 8.0 1.0": ["attentiveness"], "10.6 26.6 6.9": ["smithereens"], "2.9 15.8 6.0": ["accentuating"], "4.9 14.9 7.8": ["pushups"], "8.8 19.4 5.1": ["mockingly"], "-0.2 15.1 5.5": ["cipher"], "-6.4 9.7 24.5": ["sedimentation"], "6.8 1.6 2.7": ["diversifies"], "15.1 10.2 2.3": ["countrys"], "12.2 11.1 4.6": ["workhorses"], "-4.5 3.2 6.1": ["plotlines"], "12.5 11.8 9.1": ["masthead"], "1.6 9.6 8.2": ["impoverishment"], "1.5 3.7 15.2": ["drizzly"], "11.9 3.9 -2.0": ["innovated"], "-0.1 16.7 23.5": ["anchorage"], "0.1 3.6 -5.4": ["followings"], "-1.4 8.6 23.1": ["spoilage"], "-5.9 15.3 7.0": ["platonic"], "-0.6 1.3 1.9": ["acetone", "cepacia"], "-0.6 18.4 0.9": ["ingress"], "2.5 6.9 8.2": ["admins"], "2.1 -0.7 7.0": ["begining"], "19.9 11.0 9.4": ["ersatz"], "3.6 11.8 8.5": ["hardwired"], "5.7 15.2 1.5": ["mouthpieces"], "0.3 9.5 7.0": ["switcher"], "5.4 -0.5 8.5": ["calendaring"], "-7.1 17.2 15.8": ["bettor"], "4.2 9.1 11.3": ["undercurrents"], "7.4 6.7 4.1": ["smudged"], "-3.0 10.4 7.3": ["inbreeding"], "7.2 9.4 3.8": ["personhood"], "9.6 6.7 17.6": ["grouchy"], "-4.9 -1.4 6.3": ["bcf"], "7.5 11.4 3.8": ["unpredictably"], "1.9 13.3 8.2": ["cenotaph"], "1.0 -0.9 7.7": ["parsed"], "13.1 11.0 7.9": ["flitting"], "7.1 1.5 6.7": ["rials"], "-0.2 4.2 5.0": ["withholds"], "-3.6 2.1 7.1": ["capella"], "3.8 1.8 11.3": ["hairspray"], "2.0 17.0 2.9": ["radiance"], "0.6 8.6 1.5": ["immediatly"], "10.8 14.7 0.5": ["globalizing"], "-1.5 12.0 0.0": ["quietness"], "0.9 5.9 0.4": ["thinness"], "1.9 1.2 -0.9": ["learnings"], "0.2 4.3 -1.7": ["breathalyzer"], "17.0 0.9 3.4": ["pimped"], "7.5 1.5 11.0": ["bobsleigh"], "5.0 3.3 -0.4": ["flaunts"], "13.3 10.8 4.0": ["crackpot"], "3.7 12.2 7.8": ["innately"], "8.1 1.1 20.1": ["mocha"], "-5.1 -1.2 7.7": ["disqualifications"], "6.2 8.0 2.8": ["arouses"], "0.6 3.8 16.5": ["fabricators"], "-4.3 20.1 3.9": ["rearming"], "-1.5 6.8 9.6": ["sulky"], "-9.8 -0.5 -1.0": ["reposted"], "10.2 16.9 8.6": ["downloaders"], "15.3 12.1 1.3": ["prowled"], "4.0 11.3 1.6": ["devalues"], "18.3 4.8 17.4": ["gunk"], "2.2 6.7 22.3": ["thatch"], "30.3 13.1 20.6": ["gnome"], "-7.0 2.9 2.7": ["guesthouses"], "-1.0 14.6 9.7": ["jokester"], "0.5 2.2 14.6": ["bloomers"], "2.0 -0.6 -1.4": ["shortlived"], "-5.3 16.9 6.4": ["memorization"], "12.6 2.1 7.6": ["semiautonomous"], "6.1 16.8 11.8": ["turnbuckle"], "0.3 15.1 13.5": ["isms"], "12.5 -0.9 6.9": ["fizzles"], "12.6 12.1 9.5": ["zigzagging"], "8.4 4.6 10.5": ["pillowcase"], "5.4 8.3 13.7": ["sayin"], "17.5 11.0 7.7": ["serenely"], "5.8 8.1 29.4": ["barbecued"], "-4.2 7.4 7.1": ["unserved"], "12.8 -4.7 11.5": ["tricycles"], "5.4 21.6 -0.9": ["inquisition"], "10.8 9.4 9.0": ["stagecoach"], "0.6 19.8 2.1": ["chillingly"], "0.6 10.2 8.1": ["phonics"], "2.1 10.5 6.0": ["denoted"], "4.0 4.3 3.2": ["winnowed"], "9.3 7.0 2.6": ["retrenching"], "13.1 -0.5 4.1": ["milkman"], "3.1 6.3 5.3": ["churchyard"], "-3.9 15.2 8.5": ["mindfulness"], "-8.6 3.8 12.5": ["nonwhite"], "-1.0 12.5 1.7": ["bookmarking"], "17.9 17.4 11.5": ["matador"], "13.3 4.1 4.6": ["holograms"], "17.7 -5.8 13.1": ["paneled"], "21.5 13.3 6.2": ["slithered"], "-6.7 6.1 17.7": ["corneas"], "-3.8 2.6 -0.3": ["agronomy"], "8.9 3.6 15.6": ["aviary"], "2.4 8.2 11.8": ["localism"], "8.7 13.2 20.9": ["maples"], "7.3 6.6 14.2": ["ornamentation"], "1.9 8.2 1.8": ["displacements"], "3.4 -2.3 12.6": ["yellowed"], "1.4 10.2 7.5": ["iterative"], "17.2 5.1 12.0": ["snoozing"], "9.0 11.5 13.7": ["torpedoing"], "13.1 12.7 5.7": ["archway"], "-3.1 4.4 7.0": ["copywriting"], "12.0 7.4 -2.1": ["traipsing"], "7.2 2.1 10.9": ["beens"], "8.3 13.8 7.3": ["pollutes"], "11.5 9.4 12.0": ["gadfly"], "5.6 1.8 4.8": ["tradeshows"], "0.5 14.7 13.9": ["homo"], "14.1 13.4 6.9": ["flattens"], "8.6 1.9 7.6": ["legalese"], "-7.3 7.9 4.3": ["hurdlers"], "12.3 18.2 15.1": ["battler"], "0.0 2.8 6.4": ["athenahealth"], "6.4 10.8 5.5": ["hemispheres"], "6.7 14.5 12.8": ["pheromones"], "6.6 -5.5 4.3": ["cinched"], "3.5 2.1 25.4": ["puddings"], "-4.1 15.4 -2.6": ["equivocation"], "-6.0 10.2 7.8": ["reunify"], "8.4 12.1 8.7": ["forefinger"], "13.4 7.4 13.6": ["tutu"], "6.7 5.7 13.6": ["stencils"], "4.1 12.5 10.3": ["skinhead"], "17.9 11.3 13.6": ["natch"], "-1.7 -4.3 12.5": ["milks"], "3.3 8.2 3.1": ["ached"], "10.7 2.6 -5.5": ["interactively"], "9.4 -0.3 13.4": ["capper"], "2.6 14.9 8.2": ["metastasized"], "4.4 4.5 5.2": ["cosmonauts"], "4.0 11.7 11.2": ["leashed"], "-4.4 11.6 17.2": ["fawns"], "-2.4 5.9 9.9": ["thorium"], "8.6 0.5 5.0": ["pervade", "menos"], "-4.0 9.2 14.8": ["mothering"], "7.2 7.2 12.8": ["metrosexual"], "14.9 15.8 27.2": ["fireflies"], "10.9 8.5 11.3": ["pimples"], "10.5 9.1 -2.5": ["intercompany"], "-3.4 6.9 12.5": ["frac"], "0.9 3.6 5.4": ["snowiest"], "-0.6 3.4 7.3": ["optometry"], "-1.3 3.7 1.9": ["generality"], "16.7 6.8 21.2": ["rhinoceros"], "2.5 5.2 6.8": ["applicator"], "11.6 6.9 6.6": ["rewire"], "9.8 2.5 2.9": ["conning"], "13.3 8.7 2.9": ["ogling"], "1.5 20.0 4.4": ["eventualities"], "1.5 8.2 12.8": ["clotheslines"], "22.9 9.9 7.8": ["lasso"], "9.3 12.5 10.4": ["prongs"], "3.2 40.1 10.6": ["foxhole"], "-4.5 9.0 3.0": ["unforced"], "-0.2 11.6 2.8": ["lynch"], "0.6 4.1 -0.1": ["unisex"], "2.5 1.3 7.2": ["logins"], "-1.5 -2.7 5.2": ["butane"], "10.0 7.9 12.0": ["flab"], "9.9 5.6 13.0": ["torsos"], "4.4 5.7 19.5": ["scat"], "0.2 -0.7 -5.8": ["incharge"], "0.7 7.1 2.2": ["dismally"], "0.3 22.4 43.0": ["baitfish"], "23.0 22.9 5.6": ["superman"], "0.6 3.2 9.8": ["mandal"], "0.2 0.5 2.5": ["freshening"], "0.0 1.2 11.6": ["florals"], "2.5 17.0 4.7": ["quitters"], "15.9 37.0 21.8": ["battleships"], "-0.5 3.4 25.2": ["peppery"], "4.1 16.0 1.8": ["leaderless"], "-6.7 -2.1 14.5": ["vasectomy"], "-8.5 18.2 -3.0": ["unacknowledged"], "11.2 16.4 -6.6": ["vilifying"], "7.8 6.7 -2.7": ["rededicated"], "5.2 5.7 18.9": ["tans"], "4.3 2.1 9.5": ["paraffin"], "2.1 12.5 -0.5": ["blinkered"], "6.7 8.7 18.3": ["crockery"], "7.3 7.3 3.2": ["reassuringly"], "8.6 4.1 3.9": ["palmed"], "9.6 -0.4 10.8": ["coveralls"], "0.0 16.0 9.0": ["unmotivated"], "-8.9 5.6 0.2": ["outspokenness"], "2.6 15.1 8.9": ["nihilistic"], "-2.8 -1.9 4.2": ["nandrolone"], "11.0 5.5 8.3": ["overhangs"], "8.6 3.4 6.1": ["coining"], "13.9 1.4 25.3": ["emu"], "-0.3 6.4 7.7": ["lanyard"], "8.5 7.5 3.7": ["suffused"], "1.4 -3.1 5.5": ["lockups"], "4.6 -1.0 18.4": ["boned"], "-2.3 17.4 14.1": ["privateer"], "25.3 26.2 7.3": ["beachhead"], "3.9 -4.5 6.5": ["av"], "9.5 5.9 28.0": ["hazelnut"], "12.6 8.9 3.1": ["waft"], "7.9 11.4 4.9": ["stiffest"], "2.3 15.6 5.4": ["freest"], "5.4 7.9 4.8": ["juiceheads"], "6.3 2.1 5.8": ["shes"], "8.0 15.9 5.9": ["paralyzes"], "10.9 13.3 8.2": ["journos"], "3.0 5.9 27.3": ["raisin"], "3.7 13.3 12.3": ["venal"], "-2.5 15.3 1.7": ["demeaned"], "5.0 9.0 -0.5": ["inputting"], "14.6 8.8 5.2": ["explosively"], "9.8 7.9 17.5": ["griddle"], "-8.0 -1.5 4.9": ["rosiglitazone"], "-4.2 3.8 1.7": ["quarterfinalist"], "-7.9 0.7 -0.6": ["gynecologists"], "-2.8 -1.0 15.1": ["ghee"], "3.4 17.7 7.2": ["regimental"], "5.5 2.7 11.8": ["webmail"], "1.4 13.5 1.6": ["predicaments"], "-2.5 2.0 2.6": ["reinterpretation"], "7.5 16.5 22.4": ["chlorophyll"], "0.2 5.1 5.2": ["corporators"], "10.5 14.6 3.2": ["americans"], "4.3 0.8 9.6": ["stubs"], "14.4 13.9 3.5": ["inglorious"], "-6.2 -1.0 1.9": ["soundproofing"], "5.7 10.6 5.0": ["handkerchiefs"], "-4.9 2.3 1.2": ["sureties"], "11.1 1.6 45.3": ["krill"], "18.1 8.4 15.8": ["geezer"], "32.8 1.9 7.4": ["multibillion"], "5.1 15.6 5.3": ["scavenge"], "-6.0 9.0 3.2": ["abrogation"], "8.9 12.9 11.8": ["manna"], "3.9 12.8 3.1": ["obstructive"], "5.3 5.4 2.9": ["percussionists"], "5.9 12.5 14.1": ["cyclic"], "17.0 10.3 24.0": ["turnip"], "11.9 14.6 4.3": ["powerbroker"], "9.6 3.9 -2.4": ["televangelist"], "5.3 9.5 6.8": ["impulsively"], "13.5 0.9 17.1": ["bobs"], "5.9 0.5 7.3": ["polytechnics"], "21.4 10.3 21.9": ["wriggling"], "-0.9 -1.6 2.2": ["physiotherapists"], "5.8 3.8 4.1": ["gossipy"], "4.2 37.0 0.3": ["battlefront"], "-1.1 4.4 -0.2": ["contemporaneous"], "20.9 8.7 24.4": ["gecko"], "1.7 6.5 28.9": ["sangria"], "6.4 5.0 16.6": ["bathers"], "5.1 6.5 2.7": ["transposed"], "7.3 20.5 8.3": ["passageways"], "-0.3 15.3 4.9": ["contaminates"], "17.0 25.4 11.8": ["cyborg"], "7.0 -0.1 29.2": ["jalapeno"], "11.5 20.8 4.4": ["outsmarted"], "6.4 8.9 24.6": ["panini"], "3.5 5.9 2.3": ["cleanser"], "1.8 12.4 19.3": ["fluky"], "15.6 14.2 12.7": ["headhunters"], "8.5 9.4 0.2": ["clairvoyant"], "6.0 14.0 3.6": ["feign"], "7.3 -4.0 5.7": ["bustled"], "-6.9 7.8 2.4": ["abrogated"], "12.0 2.7 -1.7": ["hotseat"], "3.4 19.3 5.2": ["polarity"], "19.1 20.4 17.0": ["chessboard"], "0.8 11.0 3.4": ["recuperated"], "11.6 16.7 4.3": ["lifesavers"], "22.7 26.2 15.8": ["fireballs"], "-0.1 4.7 5.9": ["virtuosic"], "12.3 8.8 11.6": ["wordless"], "-11.6 17.4 3.6": ["armories"], "9.4 11.9 1.5": ["dethroning"], "7.8 6.2 16.0": ["capsizing"], "9.0 11.0 8.8": ["approximating"], "11.0 2.1 6.8": ["peopled"], "4.0 4.7 3.5": ["classiest"], "4.7 11.4 4.8": ["alphabetically"], "10.5 4.7 9.6": ["salivate"], "6.4 13.3 9.1": ["catastrophically"], "9.9 5.4 15.1": ["poodles"], "-1.9 3.1 3.2": ["journaling"], "6.2 21.1 15.6": ["pagans"], "-1.7 2.8 10.2": ["copays"], "4.7 7.0 5.8": ["rutted"], "1.9 5.8 19.0": ["dinnerware"], "-2.6 6.3 45.9": ["kingfish"], "3.7 5.5 5.1": ["masterwork"], "7.0 23.4 8.4": ["demagogues"], "-10.1 0.8 0.9": ["violist"], "7.3 8.4 9.0": ["satchel"], "5.3 12.1 9.2": ["inured"], "2.9 5.2 3.8": ["convalescent"], "2.4 -0.4 6.6": ["laminates"], "-2.1 3.5 21.9": ["hookah"], "9.4 -0.0 2.2": ["outgrowing"], "4.0 13.9 3.2": ["secrete"], "8.4 7.2 10.2": ["foretell"], "12.4 0.9 3.9": ["extendable"], "3.5 1.4 10.3": ["slackened"], "-10.0 21.8 8.1": ["shura"], "14.2 4.8 3.8": ["disassemble"], "3.4 17.8 -1.7": ["putsch"], "-4.8 5.3 6.8": ["tpd"], "3.9 6.1 13.9": ["convivial"], "5.0 19.4 6.1": ["scumbag"], "0.3 8.7 12.3": ["apportion"], "5.4 8.2 7.5": ["cuter"], "8.5 3.7 6.2": ["ephemera", "tshirts"], "-4.0 15.2 5.0": ["tactful"], "17.7 10.7 -1.1": ["vibrates"], "6.8 2.3 7.3": ["decoupled"], "6.7 -0.6 8.0": ["wi"], "10.6 10.6 14.3": ["coastguards"], "35.8 19.7 6.8": ["overlords"], "5.5 6.2 4.4": ["messier"], "8.0 11.0 0.7": ["alighted"], "3.0 11.3 3.1": ["unhittable"], "-7.3 16.4 13.0": ["zingers"], "-1.1 7.5 9.6": ["illiquidity"], "19.9 15.2 5.6": ["snuggling"], "13.8 6.0 10.6": ["ballerinas"], "3.9 8.7 10.3": ["pitlane"], "-2.8 10.0 11.6": ["syrups"], "-0.7 19.7 6.6": ["extremity"], "3.6 15.8 8.6": ["adulterous"], "2.3 8.1 11.9": ["aftertaste"], "-4.0 12.3 5.9": ["alertly"], "8.6 17.0 7.4": ["downdraft"], "-5.1 14.4 4.6": ["reestablished"], "2.7 4.5 -2.3": ["injectors"], "10.7 9.4 15.1": ["impish"], "5.9 6.3 9.5": ["sideshows"], "18.3 9.9 17.8": ["misshapen"], "2.9 7.0 1.4": ["synthesizing"], "8.9 0.3 9.0": ["pleated"], "11.5 6.2 8.2": ["tinny"], "11.3 16.5 3.8": ["equatorial"], "5.4 9.1 8.9": ["downcourt"], "19.1 10.1 16.4": ["pitchfork"], "8.6 17.0 12.0": ["dropkick"], "1.5 10.7 16.3": ["backhands"], "5.9 6.2 10.7": ["oscillations"], "5.0 2.2 18.5": ["delicatessen"], "11.0 13.8 10.4": ["nope"], "7.1 8.0 -2.6": ["unreliability"], "-3.5 3.7 11.3": ["colorectal"], "-5.7 17.8 32.8": ["smallmouth"], "11.1 -3.6 -4.8": ["roomier"], "20.6 10.2 13.1": ["wags"], "8.6 -0.8 1.4": ["scrutinizes"], "3.6 21.9 9.6": ["unstated"], "17.5 7.2 9.6": ["jugglers"], "-2.2 10.5 7.0": ["temblors"], "-5.0 11.2 3.0": ["courtesies"], "6.1 6.0 6.1": ["ballrooms"], "0.8 5.5 2.9": ["ruing"], "11.9 7.2 12.5": ["footie"], "9.9 5.4 0.5": ["visualizations"], "-0.2 19.6 7.2": ["incorrigible"], "-0.4 10.0 3.9": ["customizations"], "7.5 2.6 5.5": ["digestible"], "3.5 -1.1 9.0": ["stiffed"], "12.3 3.9 5.2": ["stenciled"], "-7.7 -1.4 -1.4": ["verifications"], "3.5 5.4 34.9": ["uncooked"], "9.3 4.0 4.1": ["purr"], "-1.7 12.0 5.5": ["minimization"], "-4.5 1.1 59.4": ["haddock"], "-0.7 -1.6 9.5": ["tradespeople"], "14.3 1.1 6.1": ["gulped"], "-4.8 4.1 17.6": ["caulking"], "-0.4 11.9 17.8": ["mulching"], "7.2 0.6 8.5": ["workaday"], "7.0 7.6 14.4": ["nub", "triptolide"], "8.0 9.1 24.7": ["sup"], "13.0 23.4 8.6": ["manipulators"], "7.1 2.9 20.2": ["zebrafish"], "3.2 15.2 -3.5": ["ultranationalist"], "3.8 12.7 -0.3": ["memorializing"], "10.7 21.8 0.3": ["plotter"], "12.4 3.5 3.5": ["tiptoed"], "5.9 9.7 16.3": ["barroom"], "5.8 5.8 1.8": ["goofed"], "12.3 29.2 7.9": ["godless"], "8.1 7.1 16.6": ["pokies"], "-1.0 3.8 9.4": ["pitstop"], "5.1 14.4 6.8": ["masochistic"], "16.9 1.5 11.4": ["sags"], "7.1 3.5 4.9": ["wristed"], "5.3 2.8 9.4": ["buildout"], "2.3 21.1 10.3": ["narcissist"], "4.3 11.0 5.0": ["unmonitored"], "14.2 6.9 15.0": ["cookers"], "7.8 8.3 22.4": ["hind"], "1.5 8.1 8.4": ["verandah"], "-5.7 6.6 7.6": ["hydrological"], "3.9 8.7 13.8": ["weaver"], "-9.3 5.0 9.9": ["prednisone"], "4.8 6.6 7.7": ["phenotype"], "-2.8 12.8 4.1": ["empirically"], "16.9 13.6 15.3": ["avarice"], "15.6 12.4 3.0": ["crackled"], "3.5 4.1 31.9": ["haggis"], "9.9 10.4 9.1": ["volcanos"], "1.1 7.1 3.5": ["imbibing"], "2.1 6.7 -5.7": ["reacquired"], "3.1 10.9 7.3": ["nauseated"], "13.9 15.2 4.8": ["cloaks"], "-0.0 -0.3 7.5": ["cursive"], "7.1 0.3 7.4": ["ethernet"], "6.5 1.9 19.8": ["roaster"], "12.1 8.3 12.5": ["juggler"], "-0.5 12.6 5.7": ["playability"], "9.1 3.6 0.2": ["bulkier"], "7.1 5.3 2.1": ["spouted"], "11.6 17.7 2.1": ["desecrating"], "4.8 16.1 8.8": ["constrict"], "9.7 6.8 -2.4": ["lavatories"], "3.3 4.4 10.9": ["doormen"], "8.8 11.0 6.3": ["circumvention"], "10.5 0.6 6.8": ["binges"], "6.3 6.3 6.3": ["goodnight"], "-2.4 6.5 2.4": ["progressions"], "1.1 2.1 12.9": ["ethane"], "4.0 8.3 4.1": ["armbands"], "4.8 0.3 11.3": ["clawback"], "-7.7 4.7 1.1": ["debaters"], "7.0 14.7 7.0": ["impostors"], "8.0 10.5 12.7": ["deke"], "4.1 9.0 11.8": ["boxoffice"], "4.4 1.5 5.0": ["reconditioned"], "14.0 -2.3 9.8": ["pigtails"], "4.3 11.0 4.0": ["bantering"], "-3.0 16.8 -2.0": ["pogroms"], "11.6 10.5 11.5": ["ballsy"], "0.2 1.4 5.4": ["resentenced"], "-0.7 12.4 3.1": ["unconstrained"], "-0.4 10.7 9.3": ["muddling"], "5.7 19.8 3.0": ["unwillingly"], "23.6 2.1 14.0": ["extravaganzas"], "3.2 12.7 7.8": ["atmospherics"], "10.2 9.1 11.4": ["euphemistically"], "3.0 17.3 3.7": ["evades"], "1.9 6.8 9.5": ["moping"], "3.9 11.1 12.1": ["fermenting"], "6.5 23.9 5.9": ["goading"], "12.2 1.6 11.7": ["orgies"], "5.7 19.7 5.2": ["caliphate"], "6.6 2.8 8.6": ["fiver"], "-6.0 17.9 -0.2": ["waterboarded"], "6.8 3.7 5.0": ["maladministration"], "9.1 8.0 9.7": ["trackball"], "3.2 9.6 23.3": ["condors"], "5.1 -1.4 16.6": ["kilts"], "-3.9 -1.4 2.7": ["notations"], "2.4 8.6 14.0": ["tighthead"], "9.0 11.2 12.5": ["ensnare"], "12.7 4.9 13.4": ["hock"], "-3.6 7.9 4.9": ["allele"], "11.5 22.3 5.7": ["ceaselessly"], "1.8 9.5 24.5": ["poinsettia"], "3.9 6.8 -1.4": ["badgered"], "4.4 -0.6 3.2": ["enthuse"], "-1.7 15.7 11.8": ["royalist"], "14.2 12.3 11.1": ["dweller"], "18.6 0.5 19.0": ["dolly"], "-0.1 10.3 -0.5": ["toughed"], "14.0 17.6 2.0": ["scorch"], "-4.8 27.1 -2.7": ["soldiering"], "9.3 5.7 6.7": ["relenting"], "1.0 8.9 6.3": ["transshipment"], "-4.4 2.3 34.5": ["tenderloin"], "5.4 0.6 12.0": ["flange"], "7.6 -4.3 1.1": ["revokes"], "5.6 13.5 2.9": ["vicariously"], "-5.3 -2.8 3.3": ["recruitments"], "17.4 3.6 14.0": ["scads"], "8.4 -0.4 21.5": ["toffee"], "0.2 3.5 9.6": ["parkas"], "10.0 -2.9 2.3": ["kerfuffle"], "14.6 11.4 7.1": ["dismantles"], "1.2 4.4 -1.9": ["detracting"], "14.5 -9.2 5.8": ["ponied"], "6.9 -0.0 -1.0": ["pilates"], "4.2 10.4 13.4": ["tempts"], "3.8 2.0 0.1": ["costed"], "3.2 14.1 7.0": ["misfires"], "-1.2 7.6 9.2": ["sophomoric"], "14.9 10.6 11.3": ["seductively"], "-0.5 16.9 10.7": ["unavoidably"], "-0.7 0.8 10.6": ["sachets"], "11.2 -1.0 9.9": ["lubricate"], "17.0 8.5 14.4": ["headhunter"], "5.6 6.1 10.6": ["misalignment"], "-0.6 -1.6 7.2": ["lithographs"], "-0.3 -2.1 4.1": ["cosponsors"], "6.0 30.3 3.2": ["airforce"], "6.5 4.7 4.7": ["derails"], "-2.8 5.7 4.9": ["coupes"], "0.9 5.8 4.4": ["cheapen"], "-0.2 -2.7 8.9": ["menopausal"], "-1.8 3.0 4.4": ["parsonage"], "12.6 10.8 2.3": ["untethered"], "-7.8 10.8 4.9": ["irrigating"], "9.6 6.4 3.8": ["creeped"], "-5.4 7.8 -0.2": ["endogenous"], "-1.0 5.7 15.3": ["dubstep"], "10.9 2.2 14.0": ["testes"], "-2.0 13.7 6.7": ["uppercuts"], "-5.4 3.7 0.3": ["listenership"], "2.1 10.8 7.4": ["pigeonhole"], "7.5 7.6 7.0": ["snore"], "14.6 10.0 5.6": ["ricocheting"], "2.7 27.6 5.7": ["scoundrel"], "-9.8 1.4 8.6": ["dressy"], "6.0 -2.1 11.3": ["thalidomide"], "5.9 12.4 35.9": ["herons"], "4.1 12.5 2.4": ["behoove"], "3.7 14.8 4.1": ["exaggerates"], "4.1 8.8 6.0": ["briefest"], "21.6 11.0 15.4": ["bulbous"], "13.5 5.9 2.7": ["imitates"], "-10.5 4.2 2.9": ["antihistamines"], "9.4 3.4 8.3": ["ponchos"], "19.5 7.8 7.4": ["majestically"], "-4.5 -0.6 -4.0": ["sensitizing"], "-1.6 7.3 1.6": ["filibustered"], "11.3 14.8 33.1": ["earthworms"], "3.6 8.1 6.5": ["leaseholders"], "12.7 19.4 12.3": ["platformer"], "-0.8 5.7 12.0": ["anaphylaxis"], "9.3 2.7 16.5": ["swimmingly"], "1.9 0.6 8.1": ["uncertified"], "3.1 4.9 8.8": ["satiric"], "3.5 7.1 4.4": ["hobnobbing"], "13.2 7.0 1.1": ["dealmakers"], "2.0 8.0 10.0": ["taluk"], "6.7 11.8 6.5": ["romantics"], "7.4 19.3 -0.3": ["psychopathic"], "3.3 21.3 2.4": ["loiter"], "9.6 10.9 7.1": ["steamroll"], "2.7 17.3 3.5": ["extrovert"], "7.5 6.7 2.1": ["amalgamate"], "10.1 10.8 3.0": ["petrodollars"], "11.5 2.5 11.8": ["wades"], "-0.7 10.8 -0.5": ["dignify"], "7.7 0.0 4.3": ["teething"], "3.1 25.0 10.2": ["realpolitik"], "13.0 18.1 13.9": ["autocrats"], "-1.1 13.6 3.2": ["unread"], "1.0 17.7 1.4": ["potshots"], "9.0 8.4 10.1": ["flatmate"], "-0.7 8.9 15.0": ["atrazine"], "12.0 8.9 7.3": ["supercenters"], "9.3 2.9 0.6": ["hyperventilating"], "-4.7 16.0 8.3": ["fatalistic"], "-1.3 -6.6 3.0": ["reissues"], "3.0 10.7 13.3": ["midriff"], "7.1 9.8 3.7": ["tinderbox"], "0.9 10.2 5.2": ["edginess"], "4.7 6.0 9.8": ["ive"], "2.5 14.9 7.6": ["idealists"], "-8.3 13.9 1.7": ["imputed"], "2.9 -4.8 0.6": ["cowgirl"], "-1.2 6.0 0.3": ["resistors"], "-7.0 5.3 -1.1": ["rehearses"], "4.3 12.4 5.5": ["neutron"], "-4.6 0.6 -4.5": ["genuineness"], "9.5 3.9 13.9": ["afro"], "4.4 2.2 11.6": ["fob"], "-0.5 15.1 37.0": ["largemouth"], "-6.1 4.7 18.9": ["staters"], "14.9 7.1 14.1": ["hayrides"], "-3.9 3.0 13.6": ["sulfate"], "-1.1 6.6 11.7": ["rumba"], "1.0 10.9 6.9": ["netminders"], "-2.7 11.3 0.7": ["stigmatizing"], "0.9 3.9 2.4": ["precluding"], "12.2 6.2 7.9": ["servo"], "5.8 12.9 10.5": ["uppity"], "-1.8 12.2 17.0": ["inbred"], "-10.1 2.9 12.6": ["whiskeys"], "-2.0 5.2 -2.1": ["endorser"], "-8.1 23.4 2.8": ["alienates"], "1.3 3.3 13.2": ["needlework"], "9.4 14.5 31.5": ["yolk"], "1.0 16.5 5.3": ["debased"], "-2.9 18.2 7.3": ["veneration"], "-5.2 8.3 2.6": ["reallocating"], "-1.3 5.6 8.7": ["rightfielder"], "-8.7 6.8 4.7": ["apostolic"], "-0.1 4.2 6.1": ["binational"], "3.3 8.6 7.8": ["bootleggers"], "13.6 -10.2 9.7": ["splurged"], "12.6 7.8 11.1": ["amble"], "9.3 1.7 1.5": ["bladders"], "9.8 7.8 8.7": ["debtholders"], "4.6 3.7 5.8": ["devolving"], "19.8 11.8 7.7": ["screensaver"], "-4.1 1.8 8.3": ["macroeconomics"], "4.0 8.8 9.5": ["screwball"], "-0.9 9.7 0.5": ["psychoanalysis"], "1.5 26.7 7.3": ["defeatist"], "17.8 -8.4 0.5": ["okays"], "-1.5 11.1 2.3": ["unrepresentative"], "-0.3 14.2 4.6": ["noncompliant"], "11.4 12.6 11.1": ["hotties", "tweaker"], "2.8 4.3 16.1": ["underachievement"], "21.1 5.1 9.9": ["dangles"], "7.3 8.4 12.5": ["halfhearted"], "-8.2 9.0 5.1": ["putouts"], "-5.1 2.8 6.9": ["lockbox"], "-7.8 7.9 12.0": ["rematches"], "7.3 7.0 3.9": ["nondiscrimination"], "-3.2 10.9 11.8": ["gemcitabine"], "-1.3 20.1 10.6": ["relativism"], "4.9 15.1 3.7": ["seduces"], "-7.1 -0.7 7.8": ["electrolysis"], "3.3 5.7 10.5": ["scanty"], "-3.9 11.4 4.8": ["disordered"], "-1.4 11.1 11.1": ["flue"], "4.1 23.0 9.0": ["subservience"], "-4.2 0.3 4.2": ["preoperative"], "4.9 34.4 9.9": ["subjugate"], "-1.0 6.5 12.9": ["valentines"], "9.4 12.5 18.0": ["whiteness"], "15.7 7.4 23.3": ["ostriches"], "1.4 7.3 17.8": ["claret"], "9.8 10.4 8.1": ["ageism"], "0.3 7.7 8.7": ["cistern"], "0.6 -0.4 17.7": ["relicensing"], "2.0 3.0 15.7": ["regrowth"], "9.8 5.2 11.4": ["turgid"], "0.8 5.7 3.5": ["rankle"], "4.0 7.1 17.1": ["cookouts"], "9.6 11.0 1.6": ["blotted"], "1.5 6.1 9.9": ["bootstraps"], "1.9 10.1 9.2": ["preparer"], "-7.5 3.9 9.2": ["postsecondary"], "-1.5 10.1 16.9": ["coinage"], "0.5 13.3 6.6": ["intermingled"], "6.9 17.5 1.5": ["audibly"], "1.0 6.8 10.1": ["aneurysms"], "10.2 1.9 11.4": ["superjumbo"], "16.3 10.5 11.0": ["millstone"], "-3.6 13.9 5.9": ["resistor"], "-0.2 11.9 9.2": ["heckle"], "11.8 13.6 3.9": ["swiveled"], "5.4 6.5 4.1": ["apparitions"], "13.6 25.9 12.4": ["menaces"], "11.4 11.1 7.8": ["yawns"], "2.9 9.5 3.4": ["maximization"], "12.9 5.4 7.7": ["lubricated"], "6.0 5.0 7.6": ["greek"], "14.6 -2.2 -2.6": ["unbranded"], "-9.1 2.9 1.2": ["intercultural"], "-1.5 8.4 -7.1": ["disclaim"], "-1.2 6.1 12.4": ["theatricality"], "-4.8 7.7 2.7": ["beneficially"], "-9.1 12.7 3.6": ["drawdowns"], "10.5 0.5 5.8": ["shafted"], "6.3 5.8 21.4": ["sealer"], "-6.0 20.2 4.0": ["sarin"], "0.6 10.4 -1.5": ["abrogate"], "1.2 5.2 5.1": ["enshrinement", "songfest"], "-5.2 11.0 29.2": ["chiles"], "-4.1 5.3 -2.1": ["outstandingly"], "14.6 11.9 13.5": ["gnaw"], "9.6 8.6 24.9": ["shamrock"], "-4.8 0.1 23.8": ["dal"], "15.0 11.6 14.1": ["scarecrows"], "11.8 4.7 7.4": ["leant"], "-0.2 8.0 10.8": ["hauliers"], "3.3 8.2 17.1": ["auntie"], "16.1 15.3 13.8": ["helmeted"], "8.6 13.5 10.0": ["scabs"], "2.4 3.5 -5.3": ["familiarized"], "2.9 0.4 42.9": ["gnocchi"], "8.7 6.2 8.6": ["pleasingly"], "7.6 8.6 7.9": ["foreshadows"], "-6.4 -2.6 9.7": ["menstrual"], "0.7 6.7 8.0": ["climatologists"], "8.8 4.6 1.9": ["typography"], "-1.1 0.5 7.6": ["foothill"], "25.2 7.8 16.3": ["spindly"], "8.0 9.4 6.8": ["nippy"], "2.8 1.3 7.9": ["misspending"], "13.8 5.8 3.4": ["bulges"], "2.8 3.3 -0.1": ["raptures"], "2.4 10.5 4.9": ["immersing"], "9.6 19.5 5.5": ["allegorical"], "20.7 1.7 3.9": ["conjoined"], "4.3 4.3 6.8": ["gaskets"], "3.0 1.0 3.7": ["gazette"], "16.3 9.9 9.6": ["waxy"], "5.3 10.3 15.9": ["waterborne"], "4.7 5.0 3.2": ["asthmatics"], "3.7 -0.4 6.6": ["safaris"], "10.8 9.5 7.4": ["hitchhiker"], "2.9 8.0 3.6": ["gutty"], "-1.5 -0.6 8.6": ["nighters"], "10.3 2.1 5.9": ["bullring"], "9.0 16.4 12.0": ["jokers"], "0.1 6.8 31.3": ["limes"], "-3.1 2.3 0.2": ["nanoscience"], "-0.8 9.7 3.3": ["comparables"], "4.5 15.6 3.4": ["needling"], "-5.7 8.8 6.8": ["overshooting"], "16.6 10.9 13.5": ["lurches"], "18.0 22.6 6.1": ["extraterrestrials"], "-5.8 10.1 10.7": ["rituximab"], "5.5 2.4 -2.2": ["deploring"], "-1.0 0.6 5.4": ["multiplatinum"], "-11.0 9.8 1.7": ["biographers"], "4.0 24.3 12.2": ["dogfights"], "-4.5 8.6 7.7": ["pedantic"], "12.5 4.3 6.3": ["pulleys"], "13.8 5.7 5.7": ["fizzing"], "4.7 -1.9 12.8": ["sashes"], "5.9 15.4 7.5": ["abhors"], "-6.9 13.4 3.2": ["impugn"], "30.1 18.2 14.8": ["humanoid"], "5.2 0.9 -0.1": ["encodes"], "-9.1 12.9 -1.8": ["declassification"], "5.4 6.3 3.0": ["seventeenth"], "5.7 1.5 6.7": ["promisingly"], "6.3 18.3 8.8": ["disdainful"], "-2.2 11.9 6.3": ["legalistic"], "3.1 5.0 7.0": ["tweeter"], "25.1 24.2 8.7": ["sentient"], "10.4 6.3 7.0": ["commoditized"], "2.8 14.2 8.0": ["horseplay"], "-1.2 4.0 1.5": ["threesomes"], "-5.4 8.8 10.8": ["byelections"], "0.4 8.7 3.9": ["shirked"], "9.0 15.2 25.6": ["oar"], "16.4 13.7 7.9": ["symbiosis"], "10.5 3.5 0.5": ["topflight"], "2.0 7.7 1.0": ["noisier"], "25.0 11.0 8.7": ["heavies"], "9.9 12.9 4.2": ["chatroom"], "3.2 -4.1 12.7": ["paleontology"], "1.6 21.7 12.4": ["countermeasure"], "4.4 4.9 0.1": ["birdieing"], "6.9 9.0 5.6": ["dismaying"], "10.4 14.5 5.7": ["caricatured"], "7.0 1.4 6.4": ["nonplussed"], "-2.3 15.2 9.2": ["usury"], "11.9 16.3 5.5": ["assholes"], "5.5 6.9 2.4": ["intertwine"], "9.4 5.4 6.1": ["apoplectic"], "1.5 3.5 5.0": ["wordy"], "0.1 2.7 6.8": ["indexation"], "4.9 8.2 -0.3": ["electrocardiogram"], "0.1 9.4 7.3": ["documentarian"], "6.3 4.1 28.7": ["luau"], "4.4 8.7 9.6": ["storyboards"], "-4.1 -3.4 -6.8": ["secondment"], "1.1 23.7 11.0": ["guardsman"], "5.8 7.7 26.6": ["hibiscus"], "22.5 13.7 12.4": ["cannibal"], "10.5 9.4 11.8": ["hustlers"], "17.5 1.2 14.4": ["squeaky"], "-5.8 16.1 0.8": ["traumatizing"], "0.1 6.3 5.2": ["carjackings"], "5.6 4.7 0.6": ["yearnings"], "-9.1 -0.6 0.5": ["misdiagnosis"], "9.6 -3.4 8.2": ["photocopying"], "4.0 5.5 15.1": ["flecks"], "3.6 4.2 15.9": ["brooch"], "-0.4 5.6 7.1": ["wildcards"], "-2.4 2.8 3.5": ["preproduction"], "1.2 14.9 10.0": ["chokehold"], "12.4 8.6 6.9": ["mothballs"], "-8.5 6.2 6.6": ["virology"], "7.1 2.0 10.8": ["dirham"], "7.9 8.8 6.8": ["stingiest"], "2.3 9.5 19.6": ["antispam"], "-3.0 7.9 9.9": ["underemployment"], "-3.5 3.2 1.8": ["cellulosic"], "-3.2 12.3 0.4": ["doers"], "-0.9 13.1 10.9": ["cellblock"], "13.3 6.1 14.4": ["candlelit"], "3.9 14.3 19.1": ["thaws"], "9.3 16.5 6.4": ["blacklists"], "-3.2 0.6 1.8": ["titling"], "16.9 29.9 9.5": ["fortresses"], "-6.0 30.8 5.0": ["causalities"], "3.9 10.1 10.2": ["climes"], "9.5 0.8 16.3": ["bocce"], "11.5 13.6 31.8": ["maggot"], "4.7 12.4 0.3": ["misstatement"], "16.9 6.8 2.4": ["daubed"], "6.8 2.0 6.5": ["throughs"], "11.6 6.0 14.6": ["meatpackers"], "1.6 11.1 7.6": ["flagrantly"], "6.0 -1.7 -1.9": ["sur"], "23.1 3.9 2.9": ["fangled"], "0.3 -0.7 -3.3": ["br"], "-1.4 4.8 11.8": ["cutoffs"], "-0.8 12.1 8.8": ["fib"], "5.5 10.5 3.2": ["undiluted"], "4.1 19.0 7.5": ["depletes"], "6.1 10.6 8.6": ["parapet"], "5.5 20.1 10.6": ["protectorate"], "11.6 12.6 11.1": ["mechanization"], "2.6 5.3 14.4": ["flighty"], "9.6 6.4 8.3": ["sloshed"], "6.1 1.0 15.8": ["weightlifters"], "14.4 17.3 7.5": ["trinity"], "1.6 0.3 5.8": ["unpolished"], "-0.8 13.4 4.3": ["constrains"], "4.2 7.8 0.0": ["exuding"], "15.5 1.8 8.5": ["snugly"], "11.3 4.7 8.9": ["newsagent"], "9.4 18.4 6.1": ["horrifically"], "9.4 10.4 3.4": ["rapidity"], "13.2 11.5 8.3": ["denuded"], "12.6 7.4 7.9": ["envelops"], "3.5 3.9 6.8": ["stargazing"], "5.8 10.5 15.5": ["cuppa"], "3.5 9.1 8.8": ["lynchings"], "3.8 7.0 13.3": ["mange"], "-1.9 15.5 0.3": ["supposes"], "15.3 11.6 5.9": ["drench"], "6.4 5.0 4.1": ["bleating"], "-1.1 -2.7 0.0": ["valedictory"], "-2.8 -0.2 4.6": ["inventoried"], "5.0 4.4 8.4": ["snotty"], "19.8 9.1 1.5": ["quaking"], "17.2 1.6 7.5": ["belle"], "-4.6 1.5 -2.8": ["disqualifies"], "1.2 6.2 2.9": ["intelligible"], "-6.3 2.6 -2.2": ["autobiographies"], "-1.0 14.1 7.6": ["dalits"], "1.5 8.1 1.2": ["goaled"], "-9.4 12.7 -0.9": ["discipleship"], "-0.4 16.4 7.7": ["latrine"], "18.8 12.9 6.5": ["doomsayers"], "11.4 18.4 7.9": ["blundering"], "-0.7 18.5 7.0": ["indecisiveness"], "15.8 15.1 6.2": ["ingeniously"], "-10.5 7.1 14.1": ["assemblymen"], "18.6 10.5 16.6": ["greenish"], "10.1 10.6 0.1": ["cosh"], "9.6 4.9 29.2": ["oat"], "-4.9 -3.7 9.4": ["glycerin"], "-2.5 6.8 -1.5": ["erasure"], "7.5 6.8 11.0": ["sloppily"], "1.4 -1.4 5.8": ["miniskirts"], "-0.3 11.9 -4.3": ["rebuttals"], "13.8 4.4 12.4": ["glassed"], "-6.2 2.0 -0.2": ["harped"], "3.4 6.8 11.5": ["randomization"], "8.7 17.2 17.8": ["shard"], "11.2 11.6 2.4": ["whimpering"], "0.6 5.0 3.9": ["eighteenth"], "20.4 13.7 3.6": ["heartlands"], "1.9 11.2 6.5": ["smirked"], "5.7 10.2 19.2": ["juniper"], "6.1 10.5 12.8": ["toothache"], "19.8 19.7 13.9": ["hyenas"], "-3.7 -1.5 3.2": ["decriminalized"], "5.6 14.0 -0.9": ["embarrasses"], "-7.8 1.7 4.5": ["probationers"], "-0.4 4.4 40.5": ["shorebirds"], "0.6 8.3 3.8": ["persuasively"], "-0.4 11.1 8.2": ["achingly"], "-1.4 6.3 0.7": ["becuase"], "-7.5 -3.5 7.5": ["paralegals"], "10.1 10.4 3.6": ["enraptured"], "-1.5 5.8 -3.4": ["impugned"], "8.4 1.6 7.5": ["monday"], "-8.8 0.5 8.5": ["antiretrovirals"], "5.5 16.8 11.1": ["stooping"], "15.8 5.4 17.2": ["hairless"], "-2.3 6.1 3.1": ["statuses"], "12.8 5.1 19.5": ["wicker"], "5.3 5.3 6.2": ["festered"], "0.8 5.4 23.4": ["jalapenos"], "5.4 2.6 14.6": ["sheeting"], "6.2 7.6 7.0": ["shareable"], "5.3 11.3 6.7": ["fumigation"], "1.0 7.7 -3.5": ["obligates"], "-6.2 19.7 7.8": ["exigencies"], "2.7 2.3 3.4": ["toot"], "5.3 6.7 3.6": ["uneconomical"], "11.4 9.7 6.6": ["schemer"], "7.9 -4.2 11.6": ["dolled"], "9.3 1.7 2.7": ["upends"], "-9.5 13.6 5.9": ["undersheriff"], "11.0 7.2 8.7": ["spacesuit"], "3.3 8.9 5.6": ["transducer"], "10.4 40.0 12.0": ["warlike"], "-1.5 6.5 2.9": ["errorless"], "14.9 2.9 13.1": ["tis"], "5.8 16.3 5.2": ["diversionary"], "1.3 7.1 9.5": ["dithered"], "9.0 1.9 6.8": ["chillers"], "-1.5 -7.1 8.3": ["propylene"], "11.1 6.4 8.4": ["vacuumed"], "17.7 3.0 5.8": ["faller"], "3.6 6.6 10.3": ["colitis"], "4.6 10.9 0.3": ["ist"], "6.2 0.4 1.0": ["burg"], "3.9 7.7 13.3": ["absurdist"], "12.3 9.6 11.9": ["stabilizers"], "7.0 2.7 26.1": ["helpings"], "9.6 -0.2 0.6": ["payed"], "-9.4 14.4 17.8": ["hartal"], "-2.8 20.1 3.7": ["repressing"], "-2.7 14.8 3.6": ["unoriginal"], "14.8 14.6 17.0": ["cuckoo"], "15.4 3.8 5.1": ["popstar"], "8.0 5.6 1.5": ["thronging"], "13.7 5.7 5.0": ["dreadlocked"], "-10.0 4.1 7.9": ["reassessments"], "7.4 2.3 5.5": ["communitywide"], "2.5 14.0 1.7": ["escapist"], "-4.0 14.7 12.1": ["castmates"], "1.9 14.2 3.4": ["reframe"], "11.7 9.6 -0.8": ["forerunners"], "11.4 16.6 11.2": ["droplet"], "2.8 19.7 8.9": ["chauvinism"], "11.1 10.2 10.7": ["flub"], "-1.9 19.9 5.0": ["introvert"], "4.7 6.6 10.4": ["matrices"], "10.1 2.0 -1.2": ["los"], "9.0 6.1 15.9": ["mohawk"], "3.8 15.6 7.8": ["headlamp"], "-2.7 9.9 -1.4": ["categorizes"], "11.5 7.6 2.7": ["blenders"], "4.1 8.1 5.5": ["barrio"], "-10.6 8.6 23.5": ["muzzleloader"], "1.3 0.5 7.5": ["casks"], "-1.5 -2.1 6.3": ["powerlifting"], "18.9 8.6 18.5": ["lumberjack"], "1.3 11.6 12.6": ["chalice"], "3.3 -1.2 12.6": ["aud"], "-0.8 9.5 2.4": ["overhear"], "14.2 18.0 29.0": ["dragonflies"], "8.3 15.9 10.9": ["hurries"], "11.0 4.7 23.0": ["brownish"], "-4.6 9.4 7.2": ["ascents"], "-13.1 4.3 2.4": ["sideman"], "-1.1 9.2 21.0": ["pigmentation"], "0.3 3.8 0.1": ["suprised"], "0.6 14.0 16.6": ["atoll"], "6.5 11.4 1.3": ["jeer"], "6.4 9.0 5.4": ["godson"], "9.5 10.2 5.3": ["forsaking"], "-0.3 16.9 3.6": ["vigilantism"], "5.7 7.5 11.4": ["sparsely"], "-10.7 0.8 3.9": ["thrombocytopenia"], "2.9 10.0 9.7": ["xbox"], "5.9 2.5 7.1": ["nah"], "10.6 8.7 5.8": ["reappearing"], "2.6 10.8 26.5": ["clove"], "12.5 33.9 15.0": ["barbarian"], "-6.6 4.7 5.5": ["magisterial"], "6.3 -2.3 1.5": ["hark"], "3.9 0.1 5.5": ["canton"], "-0.9 22.2 2.1": ["undesired"], "6.8 11.5 24.5": ["moor"], "6.6 -0.1 24.7": ["prunes"], "7.4 6.2 14.0": ["superspeedway"], "8.0 4.3 9.9": ["cobblestone"], "4.4 15.7 2.8": ["humanitarians"], "9.7 12.6 35.2": ["wasabi"], "18.5 16.6 13.5": ["slither"], "5.2 1.3 1.4": ["classier"], "3.8 6.9 7.5": ["compaction"], "9.6 0.8 14.3": ["burbs"], "11.6 0.3 8.0": ["dr"], "10.9 -1.0 4.1": ["northside"], "-5.4 10.0 14.8": ["stateroom"], "8.3 9.0 3.1": ["accelerometers"], "6.3 9.5 2.8": ["legitimizes"], "11.1 3.1 4.5": ["pe"], "-1.6 5.9 9.6": ["capsaicin"], "-1.6 2.3 5.2": ["playout"], "7.9 3.2 6.4": ["piggybacking"], "-3.8 12.6 7.0": ["enumerators"], "4.1 6.4 7.8": ["slutty"], "6.2 4.8 10.5": ["neophytes"], "19.6 6.9 12.6": ["yanks"], "-4.9 0.5 5.6": ["switchers"], "-1.4 1.2 11.1": ["esthetic"], "5.3 7.0 10.2": ["doorknobs"], "7.4 -3.3 2.2": ["multimodal"], "-6.3 14.2 15.4": ["reapportionment"], "11.7 13.9 24.8": ["woodpeckers"], "2.5 8.3 5.2": ["voiceovers"], "2.0 8.7 7.9": ["racecars"], "12.8 6.7 7.7": ["tented"], "4.1 8.2 9.3": ["strum"], "5.6 6.3 4.0": ["nonfinancial"], "2.5 20.4 13.3": ["betrothed"], "-2.0 9.2 7.1": ["palpably"], "15.4 22.0 28.9": ["ravens"], "10.1 4.7 2.0": ["internationalize"], "7.9 18.1 5.5": ["autocrat"], "7.5 3.4 5.3": ["envisaging"], "9.2 5.0 4.7": ["reeking"], "5.4 2.8 4.7": ["enhancers"], "-1.7 2.7 6.0": ["microcap"], "15.5 12.2 4.3": ["buffeting"], "-6.6 14.8 5.2": ["intimation"], "8.2 14.1 5.6": ["somberly"], "0.4 4.1 3.1": ["sucrose"], "8.1 6.4 8.1": ["visors"], "12.9 11.6 0.8": ["fetid"], "11.2 6.4 6.9": ["plunger"], "11.6 14.6 9.5": ["truncheons"], "2.9 3.5 10.4": ["compositing"], "-10.4 3.3 4.4": ["unrepresented"], "-3.3 9.8 12.8": ["doxorubicin"], "6.7 17.6 11.4": ["irrationally"], "1.1 18.5 8.0": ["disembarking"], "11.7 -1.2 0.9": ["bilk"], "-10.7 11.4 13.2": ["billets"], "8.7 10.0 6.1": ["intertwining"], "21.1 17.8 1.3": ["zapping"], "7.4 14.5 8.4": ["dignitary"], "-1.9 -2.2 12.7": ["lang"], "-6.5 1.5 6.8": ["ladylike"], "-3.4 6.3 9.7": ["ferrous"], "-0.4 14.7 38.5": ["panfish"], "-1.2 -2.4 -6.6": ["endorsers"], "4.4 5.6 5.4": ["nanostructures"], "-6.8 23.0 2.4": ["pacifism"], "-5.2 1.2 10.4": ["rainouts"], "-1.3 7.7 0.2": ["haemorrhage"], "1.2 3.6 11.9": ["bookmobile"], "3.5 12.7 3.3": ["adroitly"], "7.7 10.0 7.7": ["cupped"], "12.0 20.1 8.6": ["optic"], "2.4 5.7 3.0": ["gs"], "11.7 3.4 0.2": ["sluggishly"], "10.6 3.6 -0.9": ["lounged"], "4.7 3.8 2.3": ["reformulate"], "1.2 22.1 17.7": ["yorker"], "3.4 2.1 14.1": ["schmooze"], "4.7 16.2 7.5": ["keystroke"], "-1.5 7.8 10.9": ["abbot"], "11.9 7.3 8.1": ["swindler"], "6.9 12.7 6.6": ["entrenching"], "-5.2 -4.2 1.2": ["postdoctoral"], "4.9 3.8 23.1": ["crusts"], "6.1 19.5 10.4": ["eardrums"], "-7.2 18.1 12.6": ["afield"], "1.4 8.0 12.3": ["pickpockets"], "0.2 6.1 -0.1": ["polesitter"], "-0.8 7.0 10.1": ["puzzlement"], "6.8 16.5 11.1": ["statist"], "7.5 15.9 12.0": ["nobleman"], "14.2 9.8 8.7": ["nicking"], "-4.4 13.6 7.9": ["metastases"], "0.1 6.3 -1.0": ["confirmatory"], "12.0 -4.0 3.4": ["overbilling"], "4.4 6.5 0.1": ["enthrall"], "13.4 16.8 13.6": ["dammit"], "5.9 8.4 4.5": ["scorcher"], "13.0 6.9 6.4": ["brandish"], "7.4 8.2 3.5": ["propulsive"], "-5.4 2.3 14.3": ["cremations"], "1.0 5.3 5.0": ["pentobarbital"], "14.1 5.0 7.1": ["multimillionaires"], "12.2 3.6 36.5": ["blubber"], "1.7 17.2 8.9": ["fatalism"], "10.7 8.3 4.8": ["wellspring"], "-0.1 3.8 12.9": ["garnet"], "4.8 -1.6 5.7": ["ra"], "-7.9 1.8 -2.7": ["committal"], "12.4 3.9 3.8": ["wafts"], "11.7 5.6 7.7": ["carolers"], "0.0 6.8 -0.2": ["rb"], "3.9 5.5 17.7": ["fecal"], "12.5 16.2 8.2": ["gird"], "5.8 4.4 7.3": ["smokeless"], "-9.6 1.3 11.2": ["basses"], "-7.6 0.9 19.3": ["foodgrain"], "-1.5 19.6 -0.4": ["presupposes"], "1.8 3.7 11.6": ["groomer"], "-3.4 -6.5 -7.7": ["corroborates"], "12.1 6.8 9.6": ["ogle"], "8.9 4.3 20.8": ["basalt"], "-4.6 7.1 9.4": ["whys"], "4.4 1.7 15.7": ["hairdos"], "4.3 9.7 18.4": ["snark"], "8.3 4.9 7.4": ["satiate"], "7.8 0.5 -3.1": ["greenlight"], "26.6 17.6 15.1": ["gnomes"], "2.9 7.8 10.7": ["footings"], "-0.8 2.5 8.7": ["staycation"], "22.0 12.3 6.8": ["suns"], "2.4 8.8 1.1": ["idolizing"], "2.1 15.8 10.1": ["fictions"], "2.7 10.3 -1.7": ["initiators"], "-0.6 3.6 3.0": ["preceeding"], "0.7 8.1 -4.7": ["exemplifying"], "-4.7 20.8 2.4": ["slandering"], "18.8 5.4 11.9": ["mustachioed"], "4.6 15.7 7.8": ["quarks"], "1.1 -4.0 3.0": ["onstream"], "13.0 21.3 7.0": ["colonizing"], "5.9 7.5 14.1": ["spendthrift"], "9.8 1.8 1.6": ["durables"], "-9.7 6.8 -3.8": ["monograph"], "-2.2 7.2 24.0": ["snorkelling"], "1.7 6.0 16.4": ["brickwork"], "5.3 9.9 14.1": ["firstborn"], "-1.0 7.2 11.3": ["staterooms"], "7.4 4.1 1.2": ["reasserting"], "4.0 8.6 18.5": ["irises"], "-0.7 5.9 1.9": ["amazes"], "0.1 4.3 -4.6": ["condensing"], "4.9 11.0 10.0": ["soundscape"], "-0.5 8.3 6.7": ["slotback"], "6.9 12.8 24.3": ["conifers"], "3.3 4.2 6.9": ["filament"], "-5.0 16.7 13.5": ["habeas"], "5.2 -1.9 20.1": ["shavings"], "6.4 0.9 11.1": ["cartooning"], "5.7 12.1 19.2": ["gatherers"], "8.0 5.4 2.5": ["reek"], "10.4 -0.0 17.3": ["biotechs"], "14.0 1.8 0.0": ["showplace"], "5.1 9.9 10.4": ["dumbbells"], "-5.9 13.9 13.2": ["terroir"], "5.2 7.9 7.0": ["facetious"], "10.4 13.8 6.4": ["imaginatively"], "11.4 10.1 6.4": ["spanner"], "9.8 2.6 6.4": ["amd"], "2.7 11.2 7.7": ["patrimony"], "13.8 5.3 6.9": ["plodded"], "1.8 13.1 5.4": ["taxied"], "3.5 7.1 9.3": ["roughness"], "-8.0 1.6 10.1": ["vibrato"], "5.4 14.6 18.4": ["pheromone"], "9.5 -7.1 7.1": ["smartcard"], "3.9 12.5 10.8": ["hotness"], "1.7 5.6 11.2": ["girlish"], "7.0 7.0 3.6": ["exorcised"], "-7.0 13.1 19.3": ["breds"], "-2.2 12.3 5.9": ["descents"], "3.2 12.0 3.5": ["velocities"], "19.5 16.2 4.0": ["phobic"], "5.8 8.6 21.7": ["willows"], "-4.5 1.9 6.3": ["redecorating"], "1.0 10.0 9.8": ["geometries"], "8.7 -2.1 2.2": ["showgirls"], "-0.9 18.4 1.6": ["sadism"], "-4.7 12.6 10.0": ["fragmentary"], "8.2 2.1 9.7": ["james"], "-5.0 -0.0 4.4": ["stenting"], "-0.7 -4.6 2.4": ["adjudicating"], "-8.5 11.3 7.6": ["codeshare"], "12.2 1.6 11.0": ["armchairs"], "0.3 8.1 10.0": ["telomerase"], "-0.2 18.6 9.7": ["prideful"], "3.8 0.1 10.7": ["handrail"], "16.2 12.1 7.6": ["dystopian"], "5.0 3.3 9.8": ["ting"], "10.3 9.5 10.0": ["roadie"], "-1.5 7.3 4.8": ["deterministic"], "14.9 5.2 26.5": ["tadpoles"], "15.9 9.1 20.2": ["flotsam"], "-0.5 13.8 7.2": ["preconceived"], "5.9 14.4 10.0": ["orienteering"], "-2.5 17.4 8.4": ["overplay"], "7.5 1.9 3.9": ["polishes"], "7.8 9.6 7.6": ["virile"], "1.8 29.4 2.7": ["leaker"], "-1.9 -5.1 2.5": ["regularized"], "1.4 3.2 5.3": ["handlebar"], "9.3 -4.6 1.3": ["moonlights"], "3.4 0.7 29.3": ["suppers"], "12.3 5.0 4.1": ["bedeviling"], "-0.7 4.1 4.1": ["certiorari"], "4.2 21.1 5.3": ["gratuitously"], "-2.5 5.4 14.6": ["antebellum"], "8.4 5.3 14.5": ["juicing"], "14.9 8.8 6.4": ["staggers"], "17.4 13.7 14.3": ["hourglass"], "3.1 8.3 1.2": ["rantings"], "-6.1 -3.9 -0.4": ["concertmaster"], "7.4 5.9 13.5": ["screwdrivers"], "3.7 7.4 1.9": ["tomorrows"], "-6.0 8.1 -4.7": ["corroborating"], "-6.3 -7.9 0.7": ["postnatal"], "-1.1 -0.8 14.3": ["provincewide"], "2.6 4.8 10.5": ["simmers"], "10.1 12.5 2.4": ["woodshed"], "-3.6 -1.9 8.7": ["prasugrel"], "4.2 7.1 6.6": ["bided"], "15.7 -0.8 37.3": ["dumpling"], "5.3 7.3 19.6": ["slob"], "1.5 13.6 44.5": ["striper"], "3.7 12.1 10.5": ["slaughters"], "2.8 16.4 6.6": ["unbearably"], "-6.4 3.3 7.1": ["reapplied"], "3.4 8.9 2.1": ["inconsistently"], "12.5 13.4 14.0": ["trimaran"], "18.4 7.9 17.7": ["toon"], "10.4 13.1 12.6": ["hallucination"], "-5.3 8.2 3.1": ["madrasas"], "3.9 -0.4 8.1": ["http"], "6.5 18.6 0.5": ["prophesied"], "-0.9 8.3 6.3": ["chlorinated"], "3.9 2.1 5.2": ["hinging"], "10.5 3.2 4.0": ["wanderlust"], "-0.6 16.1 -5.7": ["accusatory"], "-2.6 4.8 5.3": ["examinees"], "5.6 7.7 -2.6": ["requisitioned"], "5.8 3.2 4.4": ["optoelectronics"], "5.2 3.4 6.0": ["webpages"], "10.9 24.7 19.9": ["mongers"], "7.5 9.0 10.9": ["hollers"], "-0.0 6.7 -0.2": ["consonance"], "7.8 12.1 11.0": ["hoes"], "8.6 5.4 3.3": ["biopharma"], "16.8 5.8 -2.8": ["wheeze"], "0.2 6.3 1.8": ["sequester"], "0.8 16.9 6.2": ["repetitious"], "-0.6 11.5 13.3": ["outcrops"], "9.9 21.3 1.6": ["steeled"], "-2.5 21.1 -1.3": ["seditious"], "-2.2 1.0 13.8": ["cardigans"], "-1.2 17.0 1.5": ["misogynist"], "-5.0 9.7 4.6": ["stakeout"], "4.3 0.4 4.4": ["canvasses"], "15.3 0.1 10.3": ["fl"], "5.1 9.5 -2.4": ["reemergence"], "9.6 4.2 2.9": ["giddiness"], "-0.6 27.2 13.6": ["absolutes"], "5.7 3.0 2.4": ["entailing"], "11.8 6.6 14.0": ["publican"], "4.6 7.9 5.6": ["frontstretch"], "1.4 -1.0 7.5": ["prostheses"], "11.5 7.5 0.4": ["compulsively"], "4.6 15.0 25.6": ["wolverine"], "4.0 0.8 13.2": ["kay"], "5.6 13.3 1.5": ["calisthenics"], "24.0 21.1 15.9": ["interlopers"], "7.0 21.1 16.5": ["camo"], "3.7 4.8 3.5": ["preconfigured"], "-3.0 15.8 6.5": ["denigration"], "-4.6 4.8 -1.3": ["paisas"], "5.3 2.0 16.6": ["stagecraft"], "1.6 9.2 -1.0": ["authoritatively"], "3.7 4.6 10.7": ["lightens"], "14.5 3.8 29.0": ["seashells"], "5.3 13.0 5.2": ["creationist"], "9.3 5.7 8.1": ["abstracted"], "7.7 10.5 6.9": ["whiffs"], "8.0 12.1 11.2": ["disfiguring"], "-14.9 13.6 11.0": ["scriptural"], "-5.4 13.0 12.2": ["commodore"], "-4.6 16.9 1.6": ["abolitionists"], "1.9 13.5 38.8": ["bluegills"], "8.2 11.7 10.5": ["caressing"], "12.4 13.3 18.6": ["jawed"], "5.8 3.0 3.4": ["outshines"], "-9.4 -1.3 12.1": ["bisphosphonates"], "8.1 6.3 -1.9": ["syncs"], "8.9 -2.7 2.2": ["hotting"], "-1.8 12.9 9.7": ["flaggers"], "25.4 -0.1 7.9": ["hitching"], "15.1 13.2 15.0": ["harbingers"], "18.4 6.8 28.8": ["crusted"], "11.0 4.4 5.5": ["perfumed"], "3.7 6.3 16.3": ["riverboats"], "13.2 14.5 12.1": ["recreations"], "11.0 8.1 11.4": ["sledgehammers"], "5.2 9.5 4.5": ["pulpits"], "17.1 -0.8 8.0": ["buoying"], "-0.4 9.9 34.2": ["mallards"], "7.0 23.6 8.4": ["unlockable"], "1.8 3.0 18.1": ["henna"], "4.4 2.3 6.5": ["interlock"], "-2.0 10.8 12.6": ["patrician"], "-5.2 13.3 45.5": ["bycatch"], "-2.6 7.3 5.4": ["snobbish"], "-3.7 -0.9 -0.7": ["lettermen"], "12.9 9.4 12.2": ["skyrockets"], "0.2 33.5 8.7": ["gunships"], "5.0 9.9 1.8": ["poser"], "21.0 12.1 25.0": ["mermaids"], "6.9 5.3 23.2": ["accompaniments"], "10.6 9.6 19.1": ["flint"], "6.6 0.5 2.2": ["pipping"], "11.1 10.2 14.2": ["flailed"], "2.4 7.3 0.1": ["unmentioned"], "13.7 0.4 13.5": ["melange"], "5.5 5.8 8.6": ["dissects"], "2.1 15.8 9.6": ["scruples"], "7.6 6.2 19.6": ["mandarin"], "6.1 -3.0 16.2": ["piquant"], "14.2 -2.5 3.7": ["fizzling"], "8.7 15.3 11.2": ["smugness"], "-1.5 -0.8 12.7": ["tix"], "-0.6 14.8 14.7": ["glioblastoma"], "-4.9 10.2 7.2": ["miscast"], "23.5 5.9 8.8": ["aglow"], "0.2 29.2 5.2": ["triangulation"], "-0.3 -0.5 27.2": ["enchiladas"], "0.0 11.5 -3.6": ["unstinting"], "-3.6 15.3 0.1": ["incites"], "4.4 8.6 9.3": ["petted"], "16.3 1.8 6.0": ["sways"], "9.7 6.2 54.3": ["shrimps"], "10.4 19.8 4.5": ["unshakeable"], "-6.0 5.5 -3.9": ["imbibed"], "3.0 11.2 11.4": ["adroit"], "-6.3 13.6 -1.4": ["extraditing"], "3.1 6.8 -2.0": ["bygones"], "8.9 4.0 5.1": ["revolves"], "12.1 26.4 16.1": ["platforming"], "1.7 0.2 3.6": ["brims"], "3.3 7.9 16.1": ["sidecar"], "-7.7 7.3 6.7": ["collegiality"], "-3.7 12.7 18.6": ["paddler"], "13.9 5.2 12.3": ["psychedelia"], "3.9 10.2 8.4": ["glaringly"], "0.8 9.2 10.5": ["markdown"], "12.8 -3.5 -0.7": ["baulked"], "17.5 17.2 25.3": ["cannonball"], "10.2 2.0 11.6": ["insubstantial"], "7.6 5.4 1.6": ["attentively"], "-7.9 4.4 11.7": ["unplaced"], "24.1 7.2 17.0": ["teeny"], "2.2 13.5 11.4": ["embellishing"], "9.8 0.3 9.4": ["yay"], "8.4 10.8 11.4": ["heliport"], "-1.8 4.8 5.3": ["sonically"], "16.5 6.2 8.9": ["walloping"], "11.9 12.1 7.8": ["toils"], "8.5 22.9 1.7": ["besiege"], "15.8 4.1 -3.2": ["pres"], "5.3 4.3 11.2": ["lathe"], "1.9 17.8 1.2": ["repented"], "13.1 5.7 10.8": ["glitterati"], "2.3 4.7 9.7": ["reflexology"], "-2.9 2.3 -0.9": ["youthfulness"], "0.0 4.3 0.4": ["bifurcation"], "5.2 3.3 3.4": ["floodgate"], "1.3 4.9 5.5": ["transits"], "-0.2 18.8 1.8": ["castigate"], "9.3 0.6 4.0": ["easternmost"], "-5.2 9.4 6.0": ["amnesties"], "2.1 4.3 8.3": ["alcopops"], "-6.6 6.7 6.6": ["baseload"], "4.6 3.5 -1.0": ["bbb"], "2.1 -2.6 8.6": ["fashionably"], "0.6 18.5 5.6": ["tactfully"], "12.8 4.8 2.1": ["checkouts"], "3.6 3.6 4.8": ["vis"], "12.0 7.5 12.6": ["misaligned"], "11.1 5.7 14.0": ["inflected"], "6.5 1.0 -4.1": ["wringer"], "16.1 23.5 9.8": ["decapitate"], "11.3 5.6 8.3": ["crucifixes"], "12.3 9.3 12.6": ["freakishly"], "13.5 24.7 8.8": ["remorseless"], "0.5 4.5 4.5": ["modulator"], "-1.2 4.6 18.5": ["abattoirs"], "5.5 6.7 2.0": ["barraged"], "-1.5 6.1 7.0": ["proteges"], "-6.3 22.5 -2.4": ["oppositional"], "9.1 1.5 11.9": ["oilpatch"], "7.0 3.0 3.9": ["bodes"], "19.6 5.2 3.7": ["hums"], "10.1 9.5 14.2": ["obelisk"], "7.4 9.5 8.2": ["assemblers"], "8.8 12.6 6.6": ["vicissitudes"], "-7.3 4.3 3.7": ["reassigning"], "12.2 16.3 8.2": ["desecrate"], "-1.8 4.3 7.0": ["tantalum"], "9.9 1.1 10.7": ["bleacher"], "-4.2 3.9 -1.0": ["undeliverable"], "1.0 12.4 1.9": ["partiality"], "12.6 6.4 0.1": ["muffle"], "17.1 11.0 6.4": ["scooting"], "3.9 -0.2 3.8": ["flunk"], "2.4 16.3 8.1": ["defecate"], "10.5 7.9 9.0": ["grandmas"], "4.8 -0.9 4.1": ["telenovela"], "1.7 4.8 2.5": ["floodwalls"], "4.3 8.9 15.8": ["circumnavigation"], "2.5 8.8 10.1": ["floorboard"], "9.3 10.8 6.2": ["lacerated"], "16.1 9.4 19.0": ["burlap"], "4.5 14.0 1.7": ["dogleg"], "0.2 5.5 -3.0": ["captivates"], "-1.2 13.4 4.0": ["workrate"], "-6.4 6.2 4.3": ["bleeped"], "-5.7 5.1 7.2": ["gravesites"], "21.8 4.9 10.5": ["warmers"], "4.8 14.3 5.8": ["blesses"], "10.6 6.5 6.1": ["extortionate"], "6.3 -1.9 20.9": ["po"], "17.8 19.1 8.6": ["bleeping"], "0.5 9.1 5.6": ["touchstones"], "-1.7 12.0 5.3": ["unsentimental"], "11.8 -1.5 2.8": ["dabbles"], "6.4 5.5 16.6": ["beehives"], "24.3 13.6 40.1": ["seagull"], "-2.9 6.5 8.0": ["sanitizer"], "8.6 9.1 5.1": ["puerile"], "-8.3 10.8 0.1": ["dissents"], "11.9 -0.7 24.0": ["lacquered"], "7.2 8.2 10.2": ["siesta"], "5.9 8.7 6.4": ["sufficed"], "4.0 12.1 7.9": ["newspaperman"], "19.3 6.9 3.3": ["castoff"], "-5.8 8.2 -1.8": ["anticoagulant"], "-0.7 22.1 7.1": ["extinguisher"], "-11.3 13.7 -1.9": ["divergences"], "17.6 10.5 8.4": ["portent"], "4.1 -7.0 3.8": ["livened"], "9.3 14.9 3.2": ["unfancied"], "-1.2 11.6 13.8": ["groomsmen"], "-0.2 18.0 0.8": ["aerobatics"], "8.1 22.0 8.1": ["opprobrium"], "2.2 10.3 16.5": ["snowmobiler"], "2.2 8.3 10.4": ["lineages"], "0.6 2.6 18.7": ["keno"], "6.0 15.6 1.3": ["decontaminate"], "-2.4 5.4 4.1": ["xii"], "23.2 14.0 31.6": ["dandelion"], "8.4 14.0 5.8": ["theyre"], "-0.8 7.3 3.0": ["clubmate"], "0.6 10.8 -4.3": ["proselytize"], "-0.6 14.0 10.0": ["anticipatory"], "2.2 5.4 5.1": ["loudness"], "2.4 11.7 8.1": ["croons"], "8.5 10.1 -0.5": ["hoodwink"], "11.8 20.0 1.3": ["pacifying"], "4.5 16.0 7.5": ["resistive"], "-3.6 1.3 4.5": ["lapsing"], "-2.3 5.3 11.6": ["hammy"], "16.0 17.6 9.9": ["oligarch"], "3.5 7.6 24.6": ["pita"], "0.5 18.5 8.1": ["sniped"], "9.8 11.8 0.5": ["somersaults"], "0.8 8.7 5.2": ["reconfirm"], "0.6 17.1 5.8": ["neighborliness"], "9.0 8.0 4.0": ["cued"], "20.2 2.7 7.1": ["nestling"], "11.4 5.3 15.3": ["backbones"], "10.8 8.6 8.5": ["botch"], "-2.7 6.4 14.5": ["widowers"], "-6.3 -2.4 9.9": ["adoptees"], "-11.7 4.7 4.8": ["gns"], "3.2 4.4 32.1": ["jambalaya"], "8.7 7.2 9.8": ["zigzagged"], "-1.8 17.2 12.9": ["overprotective"], "7.9 5.0 17.9": ["trolled"], "-0.2 1.0 13.9": ["islandwide"], "-0.6 15.0 10.6": ["wholeness"], "1.4 1.2 9.8": ["impounding"], "8.3 9.2 11.4": ["tranquilized"], "-1.0 16.0 5.7": ["astutely"], "-7.4 -3.7 13.2": ["progestin"], "5.7 7.0 12.7": ["catchall"], "-8.2 3.3 2.2": ["reexamination"], "8.2 12.5 3.3": ["pinup"], "19.6 23.4 16.3": ["interloper"], "8.6 12.9 16.2": ["husk"], "6.1 15.4 5.3": ["insoluble"], "16.3 8.8 5.0": ["kaleidoscopic"], "2.3 -3.4 7.9": ["retardation"], "15.0 5.6 13.1": ["hammocks"], "-5.5 12.3 1.1": ["scrimmaged"], "-4.2 -4.3 2.8": ["golfed"], "11.4 4.4 5.9": ["skeptically"], "6.4 3.6 29.3": ["longshoremen"], "5.1 14.2 14.7": ["godfathers"], "10.5 8.8 25.4": ["tastiest"], "-4.2 5.4 18.7": ["cabernet"], "-1.9 10.1 8.5": ["overstay"], "2.1 3.2 0.2": ["pressroom"], "-0.7 5.5 14.6": ["rowhouse"], "-5.4 1.9 -1.6": ["metabolized"], "-5.9 3.8 12.5": ["saree"], "-5.5 9.8 6.5": ["cytokine"], "-0.5 9.7 7.5": ["unemotional"], "-1.6 16.1 7.8": ["repercussion"], "-5.9 3.5 12.7": ["guineas"], "8.8 5.0 14.3": ["hawker"], "0.4 7.6 8.6": ["arthouse"], "4.7 11.2 5.6": ["invert"], "7.9 5.0 11.7": ["ultralight"], "11.1 11.2 12.3": ["salesmanship"], "1.5 12.2 2.6": ["auxiliaries"], "-1.1 22.3 5.5": ["negation"], "5.5 21.0 11.8": ["singly"], "21.9 14.8 13.1": ["devours"], "0.7 15.9 2.4": ["inoperative"], "-2.4 7.5 -0.4": ["thereunder"], "0.4 11.8 7.9": ["overgrowth"], "-0.9 -1.1 5.9": ["recapping"], "13.3 8.3 6.2": ["gimmickry"], "5.6 6.1 0.5": ["serenading"], "2.6 6.9 4.0": ["trenchant"], "5.1 11.1 11.1": ["scattershot"], "4.5 24.3 8.9": ["coldness"], "-0.4 5.8 8.6": ["occuring"], "12.5 12.9 8.5": ["quadrants"], "11.7 6.3 8.2": ["qtr"], "1.6 5.7 11.0": ["chagrined"], "14.5 16.5 18.7": ["icicles"], "8.9 18.4 5.1": ["magnanimity"], "11.7 19.3 7.0": ["reorient"], "3.7 2.4 8.6": ["recalculate"], "8.7 9.1 12.5": ["snickering"], "16.0 11.7 16.4": ["flasher"], "9.2 3.6 8.8": ["silliest"], "4.4 17.1 19.5": ["blackbirds"], "12.0 -0.9 8.9": ["sultanate"], "3.3 11.8 3.8": ["taskmaster"], "-9.3 8.2 17.4": ["turbidity"], "2.6 11.9 9.6": ["bootlegging"], "1.0 12.5 3.5": ["trachea"], "-1.4 6.2 4.7": ["insufficiency"], "4.0 11.0 3.9": ["suprise"], "9.1 7.2 -9.1": ["burnings"], "-5.3 14.4 9.4": ["pragmatists"], "-0.1 4.6 20.2": ["tows"], "1.6 1.0 8.4": ["distillers"], "5.3 4.8 -2.9": ["invalidity"], "2.2 4.0 3.1": ["pharmacokinetic"], "6.7 9.1 22.8": ["indigo"], "9.3 4.0 17.6": ["lemurs"], "-7.7 3.8 14.0": ["sarees"], "16.7 -0.5 7.5": ["unexciting"], "-6.8 12.4 -3.1": ["adherent"], "-2.8 11.8 9.3": ["metatarsal"], "-3.6 7.8 12.1": ["overdevelopment"], "3.3 5.3 25.0": ["libations"], "12.4 9.2 3.2": ["steamrolling"], "5.3 12.3 7.9": ["chirp"], "5.6 7.0 7.9": ["overlying"], "2.0 6.9 5.2": ["chide"], "12.2 4.0 14.4": ["ebony"], "5.4 6.6 0.7": ["recliners"], "4.7 7.5 10.8": ["anesthetized"], "4.8 5.9 6.1": ["clingy"], "0.5 2.5 2.8": ["extractions"], "10.2 6.1 7.7": ["teraflops"], "-6.0 5.3 3.9": ["bibliography"], "5.8 23.8 0.4": ["torments"], "3.9 4.7 29.2": ["tiramisu"], "-3.5 4.8 7.5": ["dalit"], "0.8 8.3 12.4": ["painterly"], "13.0 16.9 21.9": ["ladybugs"], "9.6 16.7 11.9": ["aboveground"], "6.2 7.4 15.0": ["reheat"], "0.2 6.8 -0.1": ["acceding"], "-0.6 1.0 8.6": ["lifers"], "9.1 0.0 8.1": ["teeter"], "2.2 7.2 5.0": ["batty"], "-3.4 6.1 29.2": ["hazelnuts"], "3.8 6.2 10.9": ["standoffs"], "9.7 8.5 0.4": ["faintest"], "6.9 9.2 8.9": ["overpopulated"], "-0.7 16.5 0.4": ["parroting"], "-3.3 10.1 15.3": ["speakership"], "14.6 6.1 9.7": ["trifling"], "5.4 14.5 19.0": ["defrost"], "5.0 3.3 -0.0": ["modulating"], "8.7 7.8 -8.3": ["resounded"], "-3.8 -0.2 1.0": ["extensibility"], "8.0 5.4 8.1": ["var"], "0.6 14.6 0.2": ["engined"], "2.5 12.4 2.5": ["relives"], "-7.3 13.9 3.2": ["moralistic"], "-7.9 12.7 4.8": ["inactivated"], "0.6 0.4 9.4": ["mufflers"], "6.0 3.6 5.3": ["shaven"], "-8.8 -2.4 9.7": ["consignors"], "8.1 12.6 14.2": ["putty"], "-5.5 5.0 7.3": ["tithe"], "-7.3 11.5 5.9": ["economize"], "20.7 18.6 15.1": ["slithering"], "-1.5 19.9 6.0": ["cryptically"], "12.1 8.4 4.7": ["parabolic"], "-1.0 5.2 8.6": ["urbanism"], "13.1 9.6 1.1": ["rampages"], "17.8 46.1 1.4": ["evildoers"], "-6.6 0.1 6.2": ["recertified"], "-8.7 7.3 7.6": ["consolations"], "-3.1 12.5 9.8": ["dispossession"], "0.7 3.7 4.8": ["nineteenth"], "10.9 19.0 6.7": ["prowler"], "20.0 4.9 27.0": ["flamingo"], "10.2 6.4 8.0": ["shrouds"], "13.0 14.6 13.2": ["schadenfreude"], "6.5 9.2 7.3": ["rubbers"], "16.2 16.0 -0.7": ["unceasing"], "10.3 8.8 -0.3": ["encyclopedic"], "-6.8 5.2 -1.2": ["modularity"], "-8.0 1.5 12.3": ["bevacizumab"], "1.4 10.2 -2.5": ["institutionally"], "14.9 11.7 10.4": ["bulldogs"], "1.4 16.2 3.1": ["sinusitis"], "17.3 3.4 12.5": ["quango"], "10.9 17.5 7.8": ["fragmenting"], "3.2 2.1 10.7": ["alloted"], "13.3 14.0 13.1": ["joust"], "8.3 10.1 3.8": ["vagabond"], "3.2 5.0 7.0": ["pontificating"], "10.1 3.4 -3.7": ["proforma"], "2.9 4.2 0.1": ["nanotechnologies"], "8.3 4.8 16.6": ["royally"], "-5.3 0.9 3.3": ["commingled"], "1.5 6.4 9.6": ["sensex"], "8.8 3.5 9.0": ["riles"], "-6.3 12.2 1.9": ["polemics"], "1.3 5.1 9.6": ["subcutaneous"], "0.1 4.2 21.8": ["groundnut"], "12.9 5.6 1.0": ["assembler"], "16.5 6.1 5.6": ["gulping"], "-2.7 0.2 17.1": ["ewe"], "18.1 11.2 15.9": ["concave"], "7.9 1.1 2.0": ["underpaying"], "9.5 7.1 11.2": ["storyboard"], "10.3 4.8 1.0": ["duking"], "0.1 11.5 -0.5": ["telegrams"], "-4.5 11.3 7.7": ["hawala"], "-2.4 23.4 16.5": ["mana"], "21.7 12.5 14.6": ["lemmings"], "3.9 17.2 21.5": ["cleat"], "8.8 16.2 9.6": ["goner"], "7.9 -6.8 3.9": ["homed"], "1.3 0.2 1.2": ["contributory"], "-5.8 8.7 3.1": ["misapplication"], "5.7 0.4 16.6": ["culls"], "0.9 20.3 2.5": ["ayatollahs"], "-1.8 4.1 7.1": ["apnea"], "-1.1 14.1 -0.5": ["exhorts"], "9.0 -7.2 1.1": ["haggled"], "7.8 5.9 -2.1": ["recoverability"], "-2.1 0.2 11.3": ["midstate"], "5.3 5.9 11.5": ["outdoorsy"], "0.2 2.6 3.3": ["laryngitis"], "-0.9 -1.1 -2.6": ["accredits"], "6.0 -5.4 0.9": ["succesful"], "-11.9 4.6 2.4": ["peacebuilding"], "3.5 5.5 0.9": ["uncontroversial"], "3.3 -0.6 38.6": ["watercress"], "30.8 11.3 10.0": ["slumbering"], "-7.8 4.9 13.6": ["oseltamivir"], "1.8 8.4 2.4": ["kmph"], "9.2 5.9 6.2": ["cropper"], "5.1 9.3 10.8": ["unwatchable"], "9.7 2.0 10.5": ["shoemaker"], "-7.8 9.3 10.4": ["presumptions"], "5.2 -1.1 12.0": ["spicing"], "7.7 8.2 4.8": ["biplane"], "14.1 10.4 11.2": ["grotesquely"], "0.1 12.3 4.5": ["extrapolation"], "10.6 2.3 2.5": ["outraced"], "4.2 6.3 8.7": ["inversely"], "4.9 16.6 9.3": ["secretions"], "10.4 3.8 4.9": ["weatherproof"], "2.5 -3.3 6.8": ["preregister"], "4.9 6.0 11.0": ["lameness", "airballed"], "11.9 36.6 -2.2": ["liberator"], "-5.1 10.9 -1.2": ["loadshedding"], "-2.9 0.3 1.9": ["reinterpreted"], "11.3 1.6 12.7": ["fizzy"], "9.1 -1.0 19.1": ["runny"], "7.2 2.1 4.2": ["revolve"], "3.6 0.5 4.7": ["deked"], "-2.0 15.3 9.6": ["pragmatically"], "16.0 0.3 3.1": ["lightbulbs"], "1.2 17.5 10.1": ["babyface"], "-4.8 6.9 12.4": ["grayer"], "10.6 2.9 32.5": ["cabbages"], "4.3 -0.7 9.2": ["ethicists"], "9.5 3.6 3.2": ["topmost"], "6.8 4.9 7.6": ["midcaps"], "5.5 2.2 12.2": ["pang"], "4.5 -1.6 8.6": ["ave"], "-13.7 6.5 9.5": ["remortgaging"], "6.7 5.6 2.7": ["livewire"], "3.9 4.7 10.3": ["acrylamide"], "12.8 3.4 4.8": ["prodigies"], "7.9 16.5 7.8": ["yardsticks"], "4.0 9.4 9.4": ["idioms"], "0.7 13.1 6.8": ["egocentric"], "9.0 19.2 3.3": ["baller"], "1.3 2.6 14.3": ["airfreight"], "-1.7 8.1 25.0": ["rubies"], "-2.8 3.0 2.3": ["transcribing"], "9.4 9.7 10.8": ["bewitching"], "-3.5 2.9 7.9": ["appropriates"], "14.3 7.2 8.5": ["tiptoeing"], "2.8 16.9 5.0": ["uncouth"], "-5.3 1.8 6.9": ["valedictorians"], "1.7 5.2 -3.8": ["hereinafter"], "7.3 3.7 2.8": ["obviate"], "24.2 11.2 14.7": ["checkerboard"], "-0.6 2.1 18.6": ["marae"], "3.1 7.9 -4.5": ["synchronizes"], "1.7 12.8 6.0": ["lascivious"], "0.2 5.7 5.8": ["guffaws"], "10.9 13.9 14.1": ["solitaire"], "4.3 3.0 4.3": ["estimator"], "12.9 9.9 20.9": ["elm"], "3.9 -1.3 6.8": ["dovetailed"], "-4.4 4.0 8.3": ["sopranos"], "0.8 7.2 4.8": ["preservationist"], "-5.2 10.7 43.6": ["overfished"], "-6.9 18.8 1.4": ["wiretapped"], "13.2 13.2 9.4": ["trojan"], "-1.3 5.9 21.3": ["shabu"], "0.6 2.8 4.8": ["ajar"], "2.9 11.0 6.5": ["persuasions"], "-1.1 3.2 17.3": ["stonework"], "-3.3 10.0 29.0": ["salsas"], "10.0 7.2 9.2": ["sandwiching"], "7.7 7.9 5.2": ["chatrooms"], "3.7 6.5 9.2": ["publicans"], "3.2 14.5 2.8": ["comprehending"], "0.4 17.8 -0.4": ["indispensible"], "9.0 13.1 6.3": ["blockading"], "0.6 7.8 -2.3": ["operationalize"], "10.0 1.5 7.0": ["usa"], "1.7 4.7 29.1": ["finches"], "-9.8 4.1 16.0": ["viticulture"], "5.7 13.0 3.5": ["journeying"], "5.8 7.5 4.1": ["chitchat"], "17.2 3.1 11.0": ["ratty"], "-0.9 8.0 15.8": ["sear"], "5.0 9.6 4.5": ["carbonated"], "5.6 18.9 2.3": ["marshaling"], "4.8 7.9 3.4": ["actualize"], "13.6 18.1 16.1": ["talons"], "-2.0 13.8 5.3": ["dogmas"], "3.8 2.5 20.0": ["taxidermist"], "2.9 -4.8 2.4": ["shoeboxes"], "20.2 -2.2 11.3": ["dotcom"], "7.2 9.3 7.4": ["unbowed"], "9.5 8.9 -1.1": ["megaphones"], "1.4 3.9 12.0": ["grassed"], "5.8 4.4 9.1": ["symmetric"], "19.9 27.7 10.7": ["kryptonite"], "10.9 1.5 2.1": ["distributorship"], "3.1 12.3 36.8": ["sinkers"], "8.9 9.8 4.1": ["pinged"], "1.8 14.3 -1.7": ["pogrom"], "13.1 7.6 10.1": ["sputters"], "0.7 19.0 8.5": ["sanctified"], "6.8 18.4 12.6": ["stasis"], "-2.0 9.2 6.0": ["formulates"], "12.6 5.9 38.4": ["radish"], "0.7 8.4 37.0": ["sailfish"], "-3.2 7.3 4.1": ["jelled"], "3.4 3.6 4.4": ["bathwater"], "3.6 8.9 -1.1": ["remedying"], "2.2 8.5 28.7": ["rind"], "-2.9 15.6 12.3": ["zinger"], "7.3 9.1 8.0": ["demutualization"], "3.4 19.2 3.9": ["bloodier"], "-1.6 2.1 19.8": ["sandalwood"], "5.5 9.0 2.8": ["catfight"], "8.0 0.5 9.1": ["achy"], "4.1 8.0 7.5": ["salutary"], "7.6 3.0 3.0": ["unmodified"], "9.9 1.8 14.3": ["skein"], "6.3 12.7 3.7": ["warpath"], "-3.7 3.8 9.2": ["farmstead"], "3.4 15.4 -5.8": ["brainwash"], "1.6 14.7 5.8": ["charlatan"], "8.2 2.1 23.2": ["beetroot"], "8.3 11.3 22.0": ["condor"], "0.8 4.2 -0.8": ["evinced"], "2.7 3.1 6.1": ["bobbleheads"], "8.5 10.6 9.3": ["dimples"], "10.8 -0.8 15.2": ["napped"], "10.3 29.6 6.4": ["warmongering"], "0.8 5.9 8.0": ["understates"], "9.3 12.9 2.4": ["constricting"], "-4.0 8.2 9.1": ["carboplatin"], "19.0 3.3 10.7": ["yuppies"], "5.0 4.0 11.9": ["reheated"], "5.6 8.8 1.0": ["existent"], "1.4 13.7 6.3": ["burglarize"], "3.0 4.8 9.5": ["descriptors"], "6.1 13.6 0.7": ["transcendental"], "12.4 2.0 -0.9": ["rechristened"], "10.8 13.2 9.8": ["awesomely"], "-0.8 11.1 13.6": ["chai"], "4.1 10.5 6.9": ["jokey"], "-1.1 7.6 4.3": ["brownouts"], "8.3 13.8 11.3": ["disdained"], "1.4 2.1 29.6": ["quesadillas"], "2.9 -2.7 0.3": ["balloted"], "7.1 5.8 3.9": ["signboards"], "1.1 -3.7 12.1": ["summonsed"], "8.0 12.1 5.2": ["murmuring"], "10.2 4.5 16.2": ["zydeco"], "-10.1 4.2 4.7": ["turboprops"], "10.2 -0.0 20.2": ["creamery"], "9.7 5.0 7.4": ["foams"], "0.1 1.3 3.3": ["hematoma"], "29.8 23.9 10.4": ["fiends"], "2.0 -0.6 9.8": ["walkathon"], "13.2 32.5 6.6": ["warmongers"], "-1.9 12.3 7.9": ["allergist"], "16.9 16.6 17.5": ["flail"], "8.9 0.9 13.4": ["leotard"], "4.2 5.7 7.9": ["writs"], "2.9 14.4 5.2": ["scornful"], "9.1 6.5 -2.7": ["recommitted"], "2.9 9.9 7.4": ["hustles"], "6.5 6.3 14.1": ["curmudgeonly"], "9.8 7.5 -0.5": ["consigning"], "-0.1 5.4 1.4": ["comport"], "13.2 6.1 8.3": ["wisp"], "1.5 11.6 -1.9": ["undressing"], "-4.2 2.9 6.4": ["sunbeds", "firewire"], "9.1 8.4 0.4": ["monetise"], "3.2 3.1 5.9": ["jnr"], "10.0 10.3 1.1": ["undervaluing"], "16.3 11.7 18.4": ["hopscotch"], "14.7 13.1 27.7": ["rowboat"], "7.7 7.6 10.9": ["workbench"], "1.7 6.2 1.6": ["plasmas"], "7.5 11.9 13.0": ["carjacker"], "0.4 9.5 9.8": ["melanin"], "-2.1 15.0 4.1": ["narrators"], "9.3 5.5 4.3": ["twittering"], "2.7 5.3 -3.5": ["castigating"], "18.5 6.8 30.8": ["hotdog"], "-9.9 8.9 -0.6": ["nonreligious"], "7.6 14.6 6.7": ["overpowers"], "3.0 8.8 37.9": ["breaded"], "-1.4 6.9 6.8": ["segues"], "10.8 12.7 3.8": ["lusting"], "-8.4 1.9 4.9": ["laning"], "3.3 5.8 3.2": ["extols"], "-1.4 3.5 3.2": ["apprenticed"], "9.7 9.1 1.7": ["slipstream"], "-0.8 5.9 1.9": ["permanency"], "5.9 15.7 14.6": ["defensiveness"], "-8.0 7.3 15.7": ["seder"], "1.3 5.6 -3.5": ["arrhythmias"], "4.7 7.3 4.3": ["luger"], "1.8 23.9 4.0": ["impure"], "6.0 17.7 6.7": ["horrendously"], "16.0 10.6 20.4": ["harvester"], "13.5 2.2 12.3": ["spacey"], "-9.5 15.1 5.7": ["theologically"], "4.2 2.1 9.8": ["valium"], "-0.7 11.5 7.5": ["despaired"], "7.5 -5.1 5.0": ["pizazz"], "-6.0 13.0 10.4": ["housebreaking"], "4.3 5.8 8.8": ["winnow"], "1.8 8.2 -4.3": ["smoldered"], "4.8 4.2 29.4": ["ladle"], "-5.8 11.3 0.9": ["circumscribed"], "8.6 3.8 9.5": ["onramp"], "0.3 5.2 8.6": ["unemployable"], "-1.8 8.4 4.4": ["illegitimacy"], "4.0 3.8 15.0": ["woolen"], "-4.1 21.0 11.4": ["partymen"], "1.2 11.5 7.6": ["tilled"], "4.1 3.0 5.6": ["railroading"], "6.9 0.1 34.6": ["parmesan"], "-1.3 26.0 15.5": ["micromanagement"], "9.6 8.8 13.3": ["indecipherable"], "14.9 4.6 8.0": ["playpen"], "1.7 15.8 0.9": ["flagbearer"], "2.4 12.5 34.4": ["shiners"], "8.1 7.0 10.9": ["spacesuits"], "16.8 9.9 8.0": ["erm"], "-2.6 -0.7 11.7": ["regency"], "7.0 18.9 4.4": ["maddeningly"], "9.1 8.4 1.7": ["dreamland"], "8.5 18.5 10.0": ["clicker"], "12.0 8.7 15.4": ["firs"], "5.8 19.7 1.1": ["sandbagged"], "3.8 10.0 -0.6": ["coherently"], "30.2 3.7 8.7": ["thingy"], "20.3 7.7 -1.4": ["troubleshooter"], "6.1 19.6 13.6": ["unawares"], "-7.6 4.3 7.1": ["gigging"], "5.8 3.2 11.6": ["conventioneers"], "8.3 28.9 4.0": ["bayonets"], "5.5 0.6 8.3": ["swabbed"], "-3.6 12.8 3.1": ["criticality"], "8.4 0.8 5.8": ["showgirl"], "2.5 5.7 5.2": ["manat"], "-1.0 14.6 10.4": ["matchplay"], "10.5 -4.7 0.9": ["por"], "2.1 13.1 4.9": ["strikeforce"], "5.4 10.0 5.7": ["earthworks"], "13.7 8.8 19.5": ["thickly"], "1.4 5.7 9.3": ["futsal"], "-7.8 6.7 7.2": ["correctable"], "7.9 16.6 3.6": ["loathes"], "7.9 9.7 13.6": ["hayride"], "-1.0 -0.1 16.9": ["hui"], "-5.9 3.5 7.7": ["prematurity"], "-2.0 3.2 8.9": ["ruminations"], "9.2 3.6 13.3": ["prog"], "-5.1 21.9 7.4": ["infliction"], "11.4 14.3 15.0": ["glumly"], "4.2 18.8 8.9": ["loudmouth"], "12.2 14.9 9.7": ["kowtowing"], "2.0 1.6 15.2": ["nan"], "-5.6 2.4 5.2": ["postproduction"], "3.0 3.6 5.6": ["uncheck"], "-0.2 2.5 16.1": ["dagga"], "21.4 6.3 2.5": ["waltzing"], "-5.5 7.5 5.1": ["verbose"], "1.6 8.7 14.0": ["snowblower"], "7.0 4.6 15.2": ["cabana"], "13.6 4.4 7.5": ["basks"], "6.7 1.1 8.3": ["bonnets"], "3.5 6.6 14.0": ["fastener"], "5.7 10.5 17.1": ["yachtsman"], "13.7 12.0 10.3": ["obscenely"], "2.0 5.0 6.6": ["distal"], "3.6 15.1 9.7": ["famines"], "-7.1 2.0 12.5": ["methylation"], "-0.8 -9.2 2.9": ["adjudicators"], "0.9 3.8 13.3": ["aromatics"], "3.8 18.1 9.8": ["obfuscate"], "-0.3 -1.8 13.6": ["inlay"], "13.0 9.3 10.4": ["bullhorns"], "3.8 5.6 27.6": ["marmalade"], "-0.2 1.8 14.0": ["mopeds"], "6.1 0.3 1.3": ["koruna"], "-5.5 10.3 5.1": ["ductwork"], "12.0 10.8 2.8": ["ascendance"], "8.4 5.9 14.7": ["centenarian"], "-3.9 15.8 7.5": ["disillusion"], "1.6 6.5 -3.7": ["evolutions"], "-3.2 6.5 6.4": ["juridical"], "-1.1 2.0 7.4": ["acupuncturist"], "3.7 6.2 9.5": ["dammed"], "-3.0 2.4 2.1": ["reevaluation"], "5.2 12.1 7.7": ["taskbar"], "7.4 19.9 5.2": ["intimidates"], "20.1 10.5 16.9": ["zodiac"], "10.6 12.9 24.0": ["honeysuckle"], "11.1 13.6 7.7": ["snowdrifts"], "8.1 19.9 11.1": ["intones"], "3.9 8.2 17.3": ["terminally"], "-4.3 10.3 1.6": ["immunities"], "0.9 4.5 9.4": ["doted"], "10.0 0.1 6.5": ["om"], "23.6 2.4 12.2": ["tastic"], "14.5 15.9 28.5": ["honeybee"], "0.1 0.1 10.1": ["satiety"], "-2.9 -5.5 5.0": ["curating"], "9.8 2.4 1.0": ["similiar"], "8.7 8.3 6.4": ["computes"], "4.4 9.5 6.5": ["bund"], "-0.8 1.9 6.4": ["informality"], "1.6 6.6 21.9": ["baklava"], "7.3 0.5 6.4": ["westside"], "10.7 6.5 3.6": ["mal"], "13.7 9.8 7.4": ["keyhole"], "5.4 25.4 5.1": ["fatherland"], "-0.9 16.7 13.4": ["headshot"], "6.7 2.9 8.6": ["creased"], "14.8 6.8 -5.4": ["blares"], "13.6 10.2 8.4": ["spooking"], "15.0 7.5 -1.2": ["retracts"], "-1.6 -1.0 8.6": ["preregistration"], "-5.1 36.6 7.0": ["airpower"], "8.7 15.8 8.2": ["devs"], "3.2 5.5 7.5": ["leached"], "-1.1 2.8 -5.9": ["condoled"], "15.4 5.2 5.7": ["superheated"], "22.5 2.5 7.1": ["grannies"], "8.3 21.8 12.2": ["sneers"], "7.0 3.9 9.9": ["thesaurus"], "-2.1 11.3 11.6": ["middleweights"], "-5.9 4.6 18.9": ["soyoil"], "5.7 6.0 8.1": ["knuckled"], "2.0 3.2 3.2": ["lat"], "4.6 19.9 8.6": ["carnal"], "1.3 7.3 15.6": ["nits"], "3.4 0.4 4.6": ["laterals"], "3.3 7.9 13.9": ["lobe"], "18.7 16.6 14.0": ["doppelganger"], "14.8 17.3 15.0": ["landmass"], "10.8 4.6 6.1": ["kaput"], "-2.0 6.3 6.4": ["glutamate"], "2.9 8.0 7.6": ["plateaus"], "-1.3 12.5 11.2": ["felonious"], "3.9 8.1 4.4": ["superconducting"], "-3.3 4.7 4.3": ["bassoon"], "10.8 16.8 4.0": ["outwitted"], "19.5 8.8 29.3": ["mottled"], "9.0 -2.2 9.1": ["malformed"], "7.0 -2.3 0.8": ["pedometers"], "2.9 -2.3 7.3": ["scrimp"], "-0.9 17.3 15.5": ["mourner"], "4.2 13.4 1.4": ["exhort"], "7.1 6.1 18.9": ["cribbage"], "1.5 9.2 27.7": ["geraniums"], "7.4 14.0 13.0": ["synonyms"], "-0.0 -3.6 7.2": ["parceled"], "-4.5 12.1 14.1": ["rakyat"], "19.8 9.5 5.2": ["epochal"], "7.0 11.3 15.6": ["petulance"], "7.7 3.6 10.6": ["selloffs"], "1.9 7.0 1.7": ["needful"], "3.8 8.5 16.5": ["housebuilding"], "4.4 -4.7 13.2": ["mga"], "-1.6 5.9 8.5": ["scriptwriters"], "10.3 11.7 15.8": ["terracotta"], "9.7 7.1 11.2": ["scrawl"], "13.7 9.2 15.4": ["gimpy"], "6.0 7.9 7.0": ["godown"], "-4.8 18.4 2.4": ["desertions"], "6.7 30.9 11.1": ["wantonly"], "7.3 11.7 6.9": ["sprayers"], "3.4 13.3 5.8": ["absolution"], "13.6 10.0 13.3": ["vixen"], "-0.2 20.0 2.2": ["denominator"], "1.4 3.3 6.0": ["bpg"], "3.7 20.0 10.3": ["paps"], "13.7 11.3 10.1": ["clobbering"], "-2.7 4.8 2.3": ["dexamethasone"], "0.1 18.2 7.3": ["readjusting"], "3.8 1.2 -2.1": ["reconditioning"], "11.5 5.3 25.0": ["crumbly"], "-4.1 13.8 9.7": ["frisk"], "-0.0 8.0 2.9": ["corporator"], "5.8 8.9 9.8": ["snobby"], "-0.2 13.7 11.5": ["anode"], "3.3 -2.2 1.1": ["waffled"], "-10.1 6.9 4.9": ["ischemia"], "-7.4 -1.0 3.4": ["repos"], "-1.4 4.7 2.0": ["leaded"], "4.0 11.0 32.3": ["offal"], "-4.4 4.8 2.5": ["theorizes"], "-0.9 10.2 6.1": ["moralizing"], "-3.6 5.9 13.9": ["suture"], "-0.4 24.5 13.5": ["cutscenes"], "16.2 6.7 23.6": ["hedgehogs"], "10.8 12.5 12.6": ["commode"], "5.8 14.5 6.0": ["reimagining"], "8.0 14.0 0.9": ["optically"], "11.9 -1.2 -0.7": ["sackings"], "-4.9 3.9 1.4": ["endovascular"], "4.7 7.5 8.4": ["floodwall"], "5.0 1.0 20.4": ["oceanside"], "12.5 5.3 6.9": ["pratfalls"], "2.3 -2.0 -0.8": ["participations"], "-2.7 -1.3 11.3": ["mainstage"], "1.9 -1.0 8.0": ["chancery"], "6.1 4.3 34.4": ["terns"], "-0.9 2.8 6.8": ["collegians"], "6.3 3.8 8.4": ["waltzes"], "5.3 14.2 13.0": ["crevasse"], "7.8 9.1 12.9": ["foreseeing"], "21.9 22.6 28.4": ["gopher"], "1.9 6.0 -0.3": ["supercharger"], "4.3 7.1 0.3": ["comparator"], "-0.3 -2.5 13.4": ["rai"], "5.4 8.6 6.6": ["centurion"], "8.6 8.5 15.4": ["bluish"], "2.2 7.8 7.6": ["concisely"], "-0.4 9.1 1.9": ["waveforms"], "18.5 4.0 6.2": ["buxom"], "2.9 18.7 13.3": ["kisser"], "9.0 4.7 17.6": ["tau"], "-10.8 6.1 -0.3": ["adoptable"], "13.5 3.2 6.0": ["hothouse"], "5.7 7.1 27.0": ["croutons"], "-7.0 3.6 3.2": ["unheeded"], "-0.3 2.5 0.2": ["hectoliters"], "4.3 10.0 14.9": ["backgammon"], "6.3 18.7 13.2": ["mountaintops"], "14.7 8.2 5.9": ["sprawls"], "3.1 2.0 9.2": ["microseconds"], "5.1 9.6 1.8": ["charitably"], "4.6 8.7 11.6": ["lowbrow"], "8.3 8.5 8.2": ["ventriloquist"], "3.6 4.9 8.0": ["sunblock"], "-3.4 2.6 9.4": ["bbls"], "12.3 28.8 10.3": ["miscreant"], "5.7 15.2 2.9": ["nobodies"], "16.6 5.0 44.4": ["heron"], "-2.9 10.4 14.4": ["wellbore"], "11.2 8.9 11.6": ["trampolines"], "-4.5 2.8 7.2": ["greenways"], "-6.3 11.7 12.6": ["incarcerating"], "16.3 4.4 3.9": ["lightbulb"], "-7.1 15.6 10.4": ["undecideds"], "-2.9 0.5 11.0": ["noms"], "-7.8 9.2 7.7": ["rosacea"], "15.7 1.5 7.4": ["agribusinesses"], "3.1 11.9 -7.9": ["evangelizing"], "8.7 6.9 0.0": ["draftsman"], "5.0 13.3 3.2": ["mope"], "8.8 6.3 8.8": ["barest"], "6.0 16.1 6.6": ["uninfected"], "9.4 6.6 13.7": ["pinches"], "9.2 18.2 13.3": ["mutters"], "4.6 12.1 20.0": ["steamship"], "7.7 6.0 0.8": ["feasibly"], "-3.2 5.4 0.5": ["metabolite"], "13.3 15.7 -2.0": ["embarassing"], "2.3 2.0 3.2": ["housebound"], "7.8 9.5 14.3": ["winnowing"], "-9.2 10.4 2.9": ["alibis"], "5.0 10.5 1.7": ["debonair"], "6.1 8.1 8.6": ["thins"], "11.8 17.4 12.1": ["outcropping"], "14.5 10.0 16.7": ["statuary"], "4.2 21.8 3.1": ["fallacies"], "5.3 9.7 22.0": ["islet"], "-4.2 1.5 7.6": ["pretreatment"], "18.5 6.8 15.9": ["mammoths"], "-5.7 13.0 -3.0": ["incommunicado"], "24.5 21.1 14.1": ["disembodied"], "17.7 -0.2 15.5": ["springy"], "9.8 7.0 0.5": ["torrential"], "3.0 18.3 18.4": ["dink"], "-9.2 0.9 -3.9": ["chaplaincy"], "3.5 9.5 9.4": ["berets"], "2.4 8.8 14.5": ["levitra"], "6.4 7.4 4.3": ["kingmakers"], "2.4 4.6 6.7": ["ragtime"], "-1.9 12.6 14.8": ["stammering"], "12.3 15.4 3.6": ["enslaving"], "1.9 8.5 5.9": ["backslide"], "1.9 -4.1 2.9": ["leavers"], "10.3 3.7 3.6": ["ambitiously"], "-2.4 -0.8 6.9": ["docu"], "-7.9 5.9 0.5": ["defibrillation"], "17.5 10.5 2.3": ["plaything"], "-9.4 2.9 8.8": ["rainfalls"], "-17.7 7.1 5.9": ["hospitalist"], "8.5 2.6 29.1": ["cashews"], "-10.4 4.5 10.3": ["fastpitch"], "15.7 6.8 7.9": ["offloads"], "13.7 34.6 5.3": ["annihilating"], "-2.7 -1.6 6.7": ["presentment"], "12.6 14.5 1.2": ["deface"], "-3.3 4.3 1.3": ["extroverted"], "-6.6 14.9 10.1": ["untreatable"], "7.1 2.9 7.0": ["begat"], "5.7 21.9 7.7": ["neoliberalism"], "5.3 -0.3 11.9": ["socials"], "1.5 11.8 15.4": ["welterweights"], "2.0 9.6 12.1": ["deuces"], "10.9 7.5 4.2": ["orbited"], "7.3 5.9 11.6": ["pleats"], "4.6 -0.2 2.0": ["cowgirls"], "3.5 10.6 16.1": ["oscillation"], "3.2 11.7 13.7": ["mimicry"], "8.5 18.3 7.5": ["undesirables"], "-5.5 9.7 2.0": ["gospels"], "-8.6 1.6 11.3": ["upcountry"], "-1.8 10.0 -3.0": ["tarnishes"], "-2.4 2.0 10.7": ["developmentally"], "2.2 -0.5 5.7": ["maxing"], "-3.2 15.4 2.0": ["drivable"], "0.6 10.9 2.5": ["detections"], "-0.1 13.8 19.3": ["nobles"], "9.2 5.3 17.6": ["drapery"], "4.9 0.9 -3.0": ["dateline"], "4.5 5.1 8.4": ["bursitis"], "8.6 2.8 6.3": ["belying"], "-2.2 2.8 1.3": ["conversed"], "1.7 11.6 8.1": ["mischievously"], "18.6 12.9 6.8": ["dominos"], "24.9 9.3 7.1": ["burp"], "7.4 4.7 8.8": ["pus"], "10.1 7.6 4.2": ["levered"], "-0.7 6.0 10.4": ["embalmed"], "24.2 18.0 2.7": ["decapitating"], "1.0 20.0 12.8": ["stammer"], "9.4 15.4 5.7": ["mutates"], "22.3 8.9 8.8": ["squished"], "14.3 7.3 5.5": ["surmounted"], "4.7 5.1 4.2": ["scribbles"], "0.9 0.8 16.3": ["turtleneck"], "9.9 18.2 2.3": ["hysterically"], "9.3 1.8 11.9": ["housemaid"], "11.1 9.7 0.6": ["heartbeats"], "8.0 2.9 27.2": ["brie"], "5.9 14.5 11.5": ["butch"], "0.0 13.0 10.8": ["hunches"], "7.3 10.8 5.3": ["astronomically"], "-2.1 -0.4 9.2": ["busking"], "4.0 4.8 8.0": ["orchestrates"], "8.7 28.8 6.0": ["villainy"], "1.1 4.2 10.0": ["nonfarm"], "5.9 5.2 9.5": ["hew"], "2.5 19.4 6.2": ["jammer"], "9.1 1.6 8.4": ["moolah"], "0.2 7.3 38.6": ["koi"], "16.0 13.2 14.5": ["yup"], "1.5 20.7 18.3": ["rook"], "10.8 0.6 14.8": ["toga"], "-3.9 13.8 12.6": ["halfbacks"], "3.1 9.1 6.8": ["immaculately"], "27.1 5.7 5.1": ["bigwig"], "2.2 18.0 9.4": ["nakedness"], "14.5 10.5 8.9": ["flit"], "8.4 4.7 8.9": ["extrapolating"], "-1.9 6.5 13.0": ["sulfide"], "-4.8 6.2 -1.4": ["emancipated"], "7.8 8.4 8.6": ["hallucinogenic"], "9.4 -3.7 7.1": ["freshers"], "3.3 15.3 8.6": ["devastates"], "3.0 7.9 12.3": ["pauper"], "14.2 5.7 14.9": ["dollhouse"], "8.5 8.6 7.1": ["perquisites"], "-7.5 -3.7 3.1": ["caddying"], "2.1 9.8 5.7": ["indigenization"], "2.1 5.3 3.0": ["mandamus"], "-8.4 10.6 7.7": ["boardings"], "5.4 3.5 13.6": ["crematory"], "2.1 8.1 -0.9": ["cortege"], "12.1 12.2 6.6": ["placating"], "3.8 1.7 10.2": ["pueblo"], "6.8 11.2 11.5": ["endearingly"], "4.0 6.5 10.2": ["smith"], "6.8 19.8 1.3": ["malcontents"], "1.2 -0.9 6.3": ["intercity"], "-0.4 -6.7 2.0": ["tidied"], "-3.2 3.0 2.1": ["dermatological"], "8.1 7.7 33.9": ["broiled"], "-7.5 5.2 1.9": ["homebred"], "-2.3 1.6 3.4": ["birthdate"], "-8.9 -1.4 14.5": ["recreationally"], "6.2 0.7 9.6": ["digester"], "-2.0 10.9 10.0": ["perfectionism"], "5.6 14.4 4.8": ["sheikhs"], "3.9 5.1 9.7": ["bratty"], "1.5 12.6 5.4": ["skydive"], "6.9 10.8 21.9": ["aspen"], "7.6 8.3 11.3": ["trinket"], "-4.3 2.5 3.4": ["hypothyroidism"], "8.1 6.3 7.9": ["stepdaughters"], "0.9 23.7 11.8": ["instinctual"], "20.7 10.2 37.1": ["walruses"], "2.3 12.6 7.2": ["grandmaster"], "-10.7 13.8 10.2": ["epee"], "6.6 0.3 9.8": ["fa"], "-11.0 5.5 2.0": ["understaffing"], "11.2 5.5 40.4": ["humpback"], "9.1 19.7 5.4": ["patsy"], "3.0 10.4 13.7": ["bs"], "7.8 25.2 7.5": ["colonialist"], "5.4 12.0 12.6": ["grownup"], "-10.3 -2.4 6.7": ["coauthors"], "4.9 16.1 28.5": ["hemlock"], "11.5 13.4 5.5": ["agonies"], "10.8 11.5 2.8": ["assails"], "-6.3 6.5 8.1": ["abovementioned"], "2.4 14.4 15.3": ["undertow"], "9.3 0.5 11.8": ["partway"], "0.5 4.3 6.4": ["carousing"], "9.0 3.8 5.0": ["ditties"], "2.6 7.4 5.7": ["supernovae"], "2.1 -5.4 6.3": ["plateaued"], "-6.0 8.2 -1.7": ["syllabi"], "4.7 19.8 14.2": ["ineptness"], "-1.2 0.5 0.5": ["presstime"], "0.7 15.9 7.2": ["tersely"], "4.4 -7.1 22.9": ["pasties"], "-2.4 2.4 8.8": ["penmanship"], "2.9 -0.5 13.1": ["strontium"], "15.7 7.0 0.5": ["enshrines"], "14.2 9.5 6.8": ["gurgling", "backlots"], "-1.6 17.8 11.1": ["encroachers"], "10.6 -0.5 11.3": ["skinnier"], "3.7 1.3 12.0": ["eccentrics"], "7.6 6.3 9.5": ["insulates"], "16.7 16.0 33.3": ["raven"], "-7.3 10.2 6.6": ["heredity"], "4.1 19.4 7.7": ["ganging"], "-4.6 2.3 8.7": ["matriculation"], "14.3 2.7 3.6": ["homewares"], "4.8 14.8 10.2": ["rots"], "2.2 -1.6 10.1": ["sublet"], "9.2 7.4 6.7": ["lampoon"], "-0.1 1.1 0.8": ["heterogeneity"], "6.2 14.9 3.1": ["fleetingly"], "1.5 10.5 3.3": ["internationalism"], "4.6 18.4 23.4": ["nematodes"], "4.2 7.2 8.2": ["kitchenette", "cautiousness"], "-4.9 10.7 7.2": ["contusions"], "2.5 11.6 -2.0": ["calibrating"], "-4.1 4.3 8.9": ["gleaning"], "17.6 -0.7 1.7": ["agog"], "11.9 19.3 6.2": ["populists"], "19.0 15.5 26.6": ["porcupine"], "-0.6 4.3 1.8": ["substantiation"], "-2.2 6.4 4.9": ["collegian"], "5.2 3.5 22.7": ["craw"], "12.4 5.4 0.1": ["bisected"], "0.3 -5.4 4.9": ["colloquium"], "14.0 -3.2 7.6": ["handprints"], "7.5 30.9 10.7": ["imperialistic"], "9.6 2.0 3.6": ["misprint"], "-1.9 5.9 10.5": ["keirin"], "-5.4 10.9 9.7": ["repechage"], "8.1 3.5 7.7": ["unearths"], "-1.1 6.1 10.5": ["cremate"], "4.3 5.8 5.1": ["propitious"], "10.2 21.4 4.5": ["tracer"], "6.4 12.7 5.0": ["preferentially"], "-6.6 4.2 -0.2": ["softswitch"], "0.2 -0.4 6.8": ["coagulation"], "8.7 6.7 3.3": ["stirrings", "signficiant"], "10.7 6.0 27.3": ["quay"], "-1.2 6.9 6.2": ["genotypes"], "1.4 2.0 0.5": ["reconnection"], "12.9 16.2 3.4": ["journo"], "-4.1 -3.2 5.7": ["preformed"], "5.8 17.8 5.5": ["soberly"], "1.1 7.0 9.5": ["betas"], "31.6 15.5 19.3": ["dwarves"], "10.2 9.5 13.8": ["planing"], "2.1 12.1 6.9": ["amen"], "3.0 7.6 27.7": ["flatbread"], "0.7 7.9 8.2": ["overlong"], "5.8 1.1 17.4": ["flatware"], "-6.6 6.6 7.5": ["choreographic"], "-10.2 6.2 12.7": ["whanau"], "13.9 22.5 9.4": ["bullseye"], "19.5 8.5 16.7": ["entrails"], "13.2 5.5 11.9": ["lop"], "5.0 3.1 28.2": ["caramelized"], "-7.5 8.1 5.7": ["stableford"], "7.6 4.5 4.9": ["glues"], "0.5 6.7 -0.7": ["hitmakers"], "3.9 9.5 20.8": ["masons"], "-3.6 8.8 2.3": ["plenum"], "4.8 6.8 9.0": ["parametric"], "5.8 -3.5 11.9": ["edu"], "-2.9 0.5 4.0": ["dc"], "0.1 1.3 8.9": ["ditzy", "nott"], "8.4 11.1 44.1": ["barracuda"], "6.9 7.6 6.3": ["flatness"], "13.6 10.8 2.3": ["globalize"], "-4.4 2.6 3.1": ["revaluations"], "-2.2 12.9 9.1": ["abortionist"], "9.5 7.7 5.9": ["saunter"], "-0.5 7.6 9.5": ["operetta"], "4.5 12.5 26.1": ["jib"], "5.6 6.1 -5.8": ["multitalented"], "13.9 6.7 5.8": ["sinuous"], "-6.0 -11.0 3.1": ["chaperoned"], "3.8 2.8 17.9": ["stepsons"], "1.1 -1.0 2.0": ["recordable"], "-0.9 2.9 -2.3": ["propositioned"], "-1.0 7.1 8.3": ["autorickshaw"], "4.0 21.9 5.7": ["misjudgments"], "7.8 7.5 12.4": ["courtly"], "3.1 15.1 10.7": ["headshots"], "5.1 4.9 15.3": ["zoologist"], "2.2 7.4 7.8": ["upmove"], "8.1 8.3 6.1": ["outhouses"], "4.1 5.6 8.2": ["bo"], "-3.3 17.4 4.1": ["hypotheticals"], "1.5 3.3 -6.1": ["spokeswomen"], "9.9 9.7 9.8": ["metalworking"], "-0.8 9.8 6.8": ["desegregate"], "3.8 2.8 12.9": ["trike"], "16.4 3.8 4.3": ["bedsheets"], "7.5 8.7 7.9": ["stepchild"], "7.9 3.5 14.1": ["mela"], "-1.7 2.0 2.0": ["hypertensive"], "-2.0 12.7 -0.5": ["misinterpreting"], "3.2 4.2 10.3": ["supercars"], "8.2 6.4 4.4": ["drawcard"], "1.9 7.6 8.4": ["dielectric"], "-3.7 6.7 -3.7": ["glossing"], "-3.0 12.1 10.7": ["aye"], "4.3 4.3 0.1": ["admonitions"], "13.5 17.8 12.1": ["hideously"], "15.1 18.8 11.0": ["interplanetary"], "7.2 5.4 25.0": ["dusky"], "18.2 8.5 6.8": ["flagpoles"], "10.7 10.3 5.2": ["pliant"], "2.5 2.5 5.0": ["ht"], "1.7 5.6 2.5": ["auditable"], "-12.1 0.8 12.5": ["broodmare"], "14.7 5.6 6.8": ["gantry"], "6.8 12.2 7.9": ["counteracting"], "2.1 8.0 3.6": ["frisson"], "9.7 7.9 32.3": ["wharves"], "-0.8 8.1 -2.1": ["trivialized"], "7.0 5.3 9.4": ["domestication"], "-2.6 14.8 8.1": ["scrimmaging"], "-0.7 12.5 6.9": ["enumerate"], "10.4 7.7 22.3": ["drumsticks"], "2.9 3.9 8.9": ["nonconforming"], "-1.4 5.9 10.0": ["quibbling"], "-1.6 2.5 15.3": ["ripened"], "11.7 12.9 11.6": ["battlers"], "5.6 -2.7 2.7": ["glamourous"], "15.5 9.7 4.2": ["reawakening"], "10.0 10.8 11.0": ["scuttlebutt"], "-4.8 1.4 2.5": ["cantor"], "12.3 6.2 6.5": ["gauzy"], "10.3 22.3 27.7": ["gobbler"], "-6.8 2.3 6.7": ["mitochondrial"], "7.0 18.3 7.0": ["peaceably"], "0.7 0.7 11.4": ["plasticity"], "-7.6 -3.7 4.7": ["caddied"], "6.2 5.9 3.3": ["twiddling"], "-0.6 9.4 27.6": ["hydrangeas"], "0.8 8.0 0.9": ["convalescing"], "-2.4 11.0 28.1": ["chillies"], "-0.5 1.8 8.8": ["mb"], "5.6 6.0 10.6": ["spinster"], "1.0 7.7 5.0": ["intracellular"], "12.9 16.3 3.2": ["supine"], "4.6 2.5 5.1": ["fondle"], "3.4 7.8 3.8": ["lavishing"], "3.4 6.7 11.2": ["apostrophe"], "-2.9 9.2 19.0": ["sakes"], "-1.3 3.4 11.5": ["raconteur"], "8.1 1.3 -0.8": ["tothe"], "-1.0 3.5 0.5": ["catalyzed"], "7.2 6.7 5.0": ["biomechanical"], "17.8 20.8 17.7": ["cannibals"], "4.9 -3.1 9.8": ["adieu"], "8.5 2.4 6.3": ["millennial"], "-3.0 3.0 1.4": ["abatements"], "-0.1 -0.6 4.3": ["quadruplets"], "0.8 10.1 -0.1": ["aerobatic"], "10.2 5.2 1.6": ["marques"], "4.6 7.3 12.9": ["draperies"], "1.0 8.5 20.4": ["curcumin"], "13.7 3.2 1.8": ["yawned"], "4.4 14.2 3.1": ["abhorred"], "9.1 4.1 -1.8": ["noncore"], "9.0 0.5 17.0": ["catnip"], "1.7 6.0 2.5": ["reevaluating"], "-2.1 11.5 4.8": ["unutilized"], "4.4 17.5 2.6": ["compunction"], "-4.2 1.9 12.0": ["proffers"], "-0.7 10.2 7.9": ["anaerobic"], "-5.0 15.2 7.3": ["dissenter"], "6.8 9.4 6.7": ["aswell"], "5.6 0.6 23.6": ["pureed"], "9.7 2.8 8.2": ["skimping"], "-2.1 0.7 12.2": ["vestments"], "14.1 4.9 14.8": ["liquefied"], "6.1 1.4 7.4": ["cabanas"], "2.4 4.7 5.0": ["hungover"], "-7.9 4.8 6.0": ["shul"], "-1.9 6.5 12.2": ["fibroids"], "10.3 15.6 -0.1": ["stridently"], "20.2 0.0 6.0": ["boomtown"], "-2.0 12.5 8.9": ["blurt"], "11.8 2.0 8.8": ["ja"], "12.6 7.7 1.2": ["expensively"], "7.4 2.1 -2.5": ["blase"], "6.6 -1.7 6.4": ["og"], "4.6 9.7 13.1": ["adornment"], "-4.6 8.9 1.7": ["invitee"], "9.5 7.4 9.3": ["homogeneity"], "21.1 4.4 17.0": ["stubby"], "5.9 -0.1 12.8": ["boardwalks"], "7.0 1.3 16.2": ["textural"], "5.7 6.3 1.2": ["unplugging"], "5.1 15.1 6.9": ["voyeur"], "3.0 19.8 6.2": ["obstructs"], "3.6 7.4 7.6": ["aqueous"], "2.4 7.2 0.7": ["abdicating"], "0.1 15.3 10.7": ["weakside"], "6.1 37.1 1.4": ["gunship"], "0.5 2.1 7.8": ["privledges"], "2.8 3.1 14.1": ["leavened"], "-0.1 8.1 4.0": ["retell"], "2.5 21.7 8.1": ["glares"], "4.9 0.4 13.2": ["ga"], "10.7 13.6 7.6": ["kowtow"], "28.8 15.6 15.2": ["cavemen"], "12.3 3.3 8.8": ["stapler"], "-1.2 5.8 4.2": ["sportsperson"], "0.9 3.4 16.2": ["starchy"], "10.4 2.1 15.1": ["cowbell"], "-8.8 2.0 8.5": ["stabled"], "-6.5 15.8 6.1": ["unitholder"], "-7.8 -0.3 0.2": ["syngas"], "2.2 6.3 -1.4": ["foward"], "0.3 11.1 17.6": ["echinacea"], "6.8 5.7 2.7": ["straightaways"], "6.9 16.0 7.4": ["demarcate"], "-4.5 -1.5 3.6": ["teleconferences"], "2.4 18.9 10.1": ["complainers"], "12.5 6.3 4.8": ["degenerating"], "-1.0 7.8 4.7": ["workhouse"], "-2.1 -0.4 13.0": ["daycares"], "-6.4 19.8 14.5": ["bluntness"], "-7.7 8.3 5.0": ["rawness"], "15.9 18.4 -0.1": ["pariahs"], "23.3 8.9 17.8": ["slurping"], "2.5 13.9 5.3": ["osmosis"], "12.2 5.9 10.0": ["cognoscenti"], "7.0 12.0 19.4": ["heather"], "4.4 6.7 15.5": ["racegoers"], "9.1 17.2 28.4": ["possums"], "4.5 -2.3 15.2": ["yung"], "6.2 11.3 14.3": ["empress"], "1.9 12.5 3.9": ["dissonant"], "-1.1 10.7 9.3": ["storages"], "12.8 8.4 -0.6": ["numerals"], "10.5 15.4 10.2": ["pugilist"], "5.3 0.0 8.3": ["blackface"], "9.9 12.1 15.1": ["mongrel"], "-0.4 3.7 11.2": ["xanax"], "4.6 10.3 17.4": ["loins"], "4.6 -1.6 16.7": ["soapy"], "10.6 12.3 5.8": ["cartwheels"], "1.1 12.0 10.1": ["emasculated"], "-10.9 0.8 15.8": ["enrollee"], "3.6 10.3 -4.0": ["breathlessness"], "-0.4 18.0 -3.4": ["gendarmerie"], "5.0 11.1 4.6": ["irreparably"], "6.9 7.4 10.7": ["prognostications"], "-4.0 2.6 3.8": ["awardee"], "3.2 9.5 9.7": ["soundbite"], "9.5 19.7 2.6": ["incontrovertible"], "-2.0 5.2 2.7": ["aldermanic"], "5.5 4.4 -0.9": ["overstates"], "8.4 0.7 4.8": ["toughens"], "0.1 12.7 7.1": ["civilly"], "11.8 15.9 13.2": ["untie"], "-8.0 12.7 13.5": ["intermarriage"], "-9.7 7.7 3.7": ["recurrences"], "-4.3 10.3 5.9": ["convalescence"], "12.7 3.7 5.8": ["counterbalanced"], "10.4 8.2 14.1": ["canaries"], "9.7 6.6 5.6": ["averts"], "1.2 22.1 3.4": ["disobedient"], "15.6 3.7 4.8": ["ambling"], "-2.3 -1.6 5.8": ["breathy"], "-5.2 13.6 -2.9": ["abscond"], "2.2 7.8 23.1": ["hickory"], "-5.9 15.0 12.2": ["politic"], "-0.7 8.0 10.9": ["blueliners"], "-1.0 13.1 7.8": ["unlivable"], "3.6 5.7 8.2": ["tabulating"], "-3.4 19.9 5.3": ["usurpation"], "0.4 4.2 7.4": ["bilingualism"], "14.3 4.3 12.8": ["beanie"], "10.5 12.8 7.9": ["pitiable"], "5.3 2.0 4.8": ["materiality"], "10.2 6.9 8.4": ["avuncular"], "9.3 5.7 6.9": ["majorly"], "5.9 10.7 8.4": ["zilch"], "1.5 4.1 8.5": ["collectables"], "-1.7 14.2 7.5": ["nonverbal"], "10.8 -2.6 8.6": ["raffling"], "2.0 6.8 4.6": ["cortisone"], "-1.8 2.0 4.0": ["outgoings"], "9.0 13.6 22.9": ["casters"], "-7.1 2.1 9.2": ["antiretroviral"], "-4.9 9.5 10.7": ["stepmom"], "2.8 -2.1 20.4": ["glucosamine"], "-0.6 2.9 7.4": ["padlocks"], "6.0 0.8 11.7": ["samplers"], "13.5 3.0 11.4": ["maxi"], "5.2 4.5 10.2": ["quarantining"], "-4.9 0.4 7.7": ["indy"], "3.4 8.6 9.7": ["euthanizing"], "12.0 -0.3 9.7": ["portico"], "1.8 -6.9 11.8": ["perm"], "2.9 2.5 3.9": ["formalizes"], "-2.1 15.2 9.5": ["lymphocytes"], "5.5 13.6 4.4": ["usages"], "16.9 8.8 19.6": ["leaden"], "6.2 11.1 9.1": ["loveliest"], "3.7 8.0 53.3": ["menhaden"], "-1.0 5.5 9.3": ["microgravity"], "17.7 8.6 8.2": ["digests"], "4.2 12.1 1.0": ["hones"], "14.9 2.0 1.7": ["stoush"], "1.0 10.8 10.0": ["backpedal"], "4.8 12.1 3.1": ["redoubtable"], "16.4 10.9 8.4": ["knifing"], "1.1 5.0 11.3": ["bromine"], "-5.1 10.1 9.4": ["seminarian"], "7.0 13.1 11.4": ["daydreams"], "21.3 13.0 19.0": ["gazelle"], "16.5 -1.2 17.9": ["shing"], "12.4 15.8 13.1": ["puzzler"], "9.4 18.1 9.3": ["hellbent"], "11.0 6.7 7.2": ["joyless"], "0.2 6.4 3.0": ["hhgregg"], "11.5 5.5 7.5": ["trendiest"], "-5.4 6.3 18.2": ["lifejackets"], "6.0 3.3 0.5": ["remanufacturing"], "19.6 7.2 11.1": ["streaker"], "6.4 7.7 6.1": ["handbrake"], "23.4 7.9 0.7": ["counterbid"], "0.4 4.6 -1.4": ["academician"], "-3.7 8.5 5.2": ["ballhandling"], "7.7 13.6 7.8": ["warhorse"], "-1.3 6.0 2.1": ["hastens"], "3.6 4.4 9.3": ["guff"], "-4.0 1.6 5.8": ["downshift"], "4.1 7.5 10.4": ["bearishness"], "3.6 18.7 1.0": ["fallacious", "ciphered"], "12.4 4.0 1.4": ["resuscitating"], "9.3 9.5 0.2": ["illegalities"], "4.5 3.0 34.7": ["ramen"], "-0.9 16.7 9.6": ["animosities"], "1.3 4.0 17.9": ["agave"], "4.9 10.1 19.8": ["candlesticks"], "10.3 11.8 5.6": ["madhouse"], "10.9 13.1 38.4": ["gull"], "-2.8 3.6 6.3": ["busway"], "-6.0 12.5 1.0": ["devotions"], "14.6 6.2 2.7": ["gradients"], "8.6 1.8 11.2": ["raincoats"], "7.0 1.5 11.4": ["marimba"], "-3.9 10.6 15.9": ["artemisinin"], "2.8 10.0 3.1": ["restrains"], "7.8 12.3 14.2": ["saucers"], "7.1 -0.9 12.8": ["neoclassical"], "9.8 2.3 3.7": ["fizzed"], "-1.0 17.0 -0.2": ["brigadier"], "1.8 13.8 7.9": ["sportsbooks"], "8.5 13.4 2.3": ["progenitor"], "-6.4 11.0 0.8": ["ascetic"], "26.6 16.8 21.5": ["totem"], "4.9 7.6 5.7": ["greenspace"], "-5.3 7.3 6.2": ["escalations"], "9.3 18.1 11.8": ["unhappily"], "3.9 7.2 -0.4": ["editorialized"], "-3.0 9.7 6.0": ["septicemia"], "3.0 11.5 -2.3": ["infact"], "2.7 5.5 10.5": ["doi"], "4.4 -1.8 3.4": ["turfed"], "9.2 2.3 10.0": ["eu"], "-1.7 3.6 7.4": ["superbike"], "13.9 10.0 8.2": ["uncannily"], "11.1 7.1 17.3": ["kitties"], "1.4 11.7 8.9": ["amity"], "-8.4 7.2 3.3": ["reviewable"], "15.1 9.9 -1.6": ["shockwave"], "2.9 15.0 7.8": ["kneeing"], "-5.3 11.1 11.4": ["setlist"], "-1.9 23.0 -5.1": ["intimates"], "0.8 8.7 -4.2": ["immerses"], "2.4 13.7 -0.5": ["outspend"], "-2.4 12.0 8.4": ["demeans"], "10.4 10.5 14.4": ["cartoony"], "0.6 8.9 12.5": ["tipple"], "8.6 2.5 9.1": ["placated"], "3.0 32.2 1.9": ["torturer"], "7.9 18.6 12.4": ["minigames"], "-6.2 4.2 0.4": ["renominated"], "10.0 16.3 9.4": ["mister"], "18.2 3.0 8.3": ["busty"], "7.8 26.6 9.7": ["flinching"], "9.2 2.6 4.2": ["erections"], "-5.7 9.6 -1.3": ["differentiators"], "12.1 20.3 21.2": ["herbivores"], "2.5 6.5 3.8": ["burnouts"], "18.1 24.4 13.4": ["dismember"], "-2.0 24.0 8.5": ["resistances"], "1.4 3.6 0.5": ["redressing"], "9.1 7.9 6.6": ["ballfield"], "13.9 2.1 15.0": ["lashings"], "8.7 2.6 -0.2": ["demoed"], "2.1 9.9 10.9": ["handloom"], "7.9 8.7 4.3": ["resurrects"], "-2.4 9.0 -0.9": ["dissuading"], "-0.6 15.8 3.1": ["forthrightly"], "3.4 25.1 9.3": ["barbarous"], "9.3 2.5 -0.9": ["axial"], "13.6 4.2 15.2": ["steams"], "17.4 9.8 26.0": ["hares"], "3.9 11.9 9.2": ["cupping"], "5.7 12.6 7.6": ["alls", "citzenship"], "-3.0 13.9 6.7": ["intemperate"], "5.5 2.7 5.9": ["teardown"], "3.6 8.8 8.2": ["reactivating"], "-1.4 -10.6 1.7": ["recapped"], "3.7 10.9 4.5": ["tradesman"], "-0.9 5.4 2.4": ["overachieved"], "5.6 12.4 13.7": ["courtiers"], "5.6 7.2 2.0": ["circuitous"], "8.1 15.9 5.1": ["severest"], "3.6 20.2 11.8": ["forechecking"], "8.0 3.0 12.0": ["photonic"], "11.2 10.7 2.3": ["bedevil"], "-4.2 3.0 6.5": ["klezmer"], "11.4 19.2 11.6": ["unidentifiable"], "7.6 21.1 20.8": ["musket"], "9.1 3.6 2.4": ["hooted"], "2.7 10.7 5.5": ["shoeless"], "10.2 2.2 4.3": ["showground"], "8.8 15.9 11.4": ["caress"], "-10.0 3.2 5.9": ["implementers"], "9.1 8.2 2.4": ["bopping"], "4.0 5.4 2.5": ["mugshot"], "13.7 23.2 17.8": ["sorcerer"], "3.8 19.7 23.7": ["voles"], "-3.8 2.2 -4.2": ["appellee"], "-6.4 -6.8 10.9": ["orthodontic"], "3.1 10.2 28.9": ["bluebirds"], "1.3 1.6 6.1": ["blemished"], "8.0 5.2 4.9": ["soundscapes"], "0.8 9.0 6.9": ["elegiac"], "0.2 6.2 8.6": ["cloudless"], "-8.3 3.0 8.4": ["micronutrients"], "6.1 7.9 2.6": ["upstaging"], "-14.4 8.4 -0.7": ["avers"], "4.6 11.3 7.5": ["mechanistic"], "-1.8 5.9 5.6": ["enduro"], "20.7 8.7 9.7": ["toymaker"], "-5.3 1.8 8.9": ["equestrians"], "10.9 14.4 3.6": ["prospers"], "15.6 3.2 12.4": ["bubblegum"], "5.5 15.9 9.1": ["nourishes"], "0.6 5.5 3.4": ["earpieces"], "-4.9 7.7 8.0": ["ji"], "10.4 5.8 -1.8": ["kindle"], "7.0 6.3 -2.1": ["restates"], "13.6 18.8 8.1": ["swindlers"], "3.8 8.5 12.8": ["mutts"], "13.2 16.8 16.5": ["chump"], "0.3 8.9 3.1": ["compellingly"], "2.7 4.0 12.0": ["axons"], "5.3 11.2 9.1": ["unrefined"], "22.4 15.6 19.5": ["streamer"], "13.7 14.5 11.5": ["bonehead"], "2.3 16.5 6.7": ["bloodhound"], "6.1 5.8 5.9": ["obigation"], "0.4 17.4 11.5": ["blowhard"], "17.1 5.3 6.3": ["multistory"], "5.0 13.4 0.2": ["severally"], "-2.0 13.0 -2.7": ["proximate"], "-0.1 4.3 11.2": ["afterparty"], "-5.4 17.7 0.0": ["anarchism"], "3.2 4.1 2.2": ["sol"], "-7.3 -4.4 0.5": ["advisement"], "0.1 6.7 9.8": ["encouragingly"], "5.2 5.3 6.6": ["laxatives"], "15.4 1.8 1.7": ["deregulating"], "3.4 1.0 2.0": ["pillowcases"], "10.3 14.4 8.7": ["hollows"], "18.0 10.8 -1.2": ["linkup"], "7.8 14.0 5.7": ["inveterate"], "7.3 7.0 1.6": ["tabulate"], "18.1 7.3 23.6": ["leathery"], "1.7 -3.7 7.6": ["tenancies"], "1.9 -3.8 4.8": ["zine"], "7.0 16.7 6.6": ["rappelled"], "15.7 0.7 5.6": ["doyen"], "0.2 2.3 9.4": ["singlet"], "4.4 12.5 -6.6": ["raters"], "0.2 -1.6 18.1": ["ferrochrome"], "1.9 4.5 18.3": ["creosote"], "-4.4 5.6 3.2": ["perfusion"], "9.8 13.5 5.8": ["hallucinatory"], "13.6 2.7 8.5": ["comely"], "4.8 11.1 13.9": ["ornithologist"], "-8.1 13.9 7.8": ["melanomas"], "-2.4 14.1 3.9": ["maligning"], "-1.5 12.4 8.2": ["likability"], "-2.6 2.5 17.4": ["ingots"], "5.3 10.4 4.8": ["haltingly"], "3.7 13.5 4.9": ["southwards"], "11.4 6.8 20.3": ["spastic"], "2.4 7.0 9.9": ["supercross"], "2.2 11.9 5.4": ["vehemence"], "0.9 9.7 8.9": ["hypothalamus"], "6.6 7.8 1.3": ["muzzling"], "-8.4 7.2 3.8": ["conditionality", "erractic"], "3.4 10.4 8.1": ["geoengineering"], "7.4 11.4 13.5": ["welts"], "-4.5 5.0 3.7": ["levelheaded"], "0.7 6.3 9.2": ["pocketknife"], "-2.7 8.2 7.9": ["bloodshot"], "7.2 20.4 3.9": ["paymaster"], "-12.5 13.4 6.2": ["lyricists"], "0.6 14.1 9.4": ["dialer"], "1.1 -0.1 -0.7": ["outraging"], "-0.5 7.9 4.3": ["dissipation"], "3.6 8.2 8.8": ["callow"], "14.0 8.8 9.2": ["clang"], "17.9 16.2 14.5": ["nouns"], "3.6 30.3 11.6": ["garrisons"], "8.7 1.8 5.6": ["cooed"], "2.7 4.6 -1.7": ["farewelled"], "12.3 14.5 7.0": ["unmolested"], "-4.6 7.9 10.5": ["recognizance"], "3.8 13.2 8.4": ["butting"], "12.8 20.1 11.5": ["moonlit"], "-8.8 1.8 2.8": ["venous"], "1.6 11.2 1.2": ["brickbats"], "6.9 15.0 1.0": ["defacto"], "13.1 19.8 6.0": ["ignoble"], "22.1 12.9 12.8": ["pimple"], "6.3 1.1 1.0": ["smoothes"], "23.8 17.6 31.3": ["dragonfly"], "5.1 20.3 11.7": ["creationists"], "-2.4 7.9 3.1": ["rustiness"], "-0.8 15.1 8.2": ["overachiever"], "-1.4 7.2 10.1": ["adventuresome"], "6.8 8.9 31.1": ["omelette"], "7.3 -1.2 7.7": ["expositions"], "-3.8 14.0 4.3": ["solvable"], "7.7 0.4 4.6": ["mixup"], "-3.6 -2.6 0.6": ["surfactant"], "10.9 8.6 18.4": ["loch"], "-4.7 32.9 2.8": ["dismounted"], "1.0 2.0 9.7": ["coking"], "7.9 11.9 4.3": ["agnostics"], "6.9 3.3 6.9": ["slacken"], "11.7 15.0 -1.8": ["barricading"], "5.4 -1.7 15.0": ["neoprene"], "6.4 4.3 5.7": ["doodling"], "10.7 5.1 15.8": ["gif"], "-1.3 15.4 15.2": ["armbar"], "4.3 7.4 5.7": ["retinue"], "-0.3 11.8 0.4": ["uncritically"], "-6.6 12.9 4.5": ["tensed"], "8.6 6.0 8.7": ["meh"], "13.4 13.9 10.4": ["leering"], "7.2 1.1 31.3": ["carvers"], "1.2 8.3 5.9": ["intranets"], "13.2 2.0 10.8": ["crooners"], "7.8 -2.1 10.6": ["bioreactor"], "5.5 15.1 2.0": ["downfalls"], "5.4 23.2 9.2": ["obeys"], "4.3 13.5 -0.1": ["insistently"], "10.3 -1.2 4.8": ["pranced"], "11.0 -1.8 16.1": ["yak"], "-7.1 3.7 7.7": ["analgesics"], "0.5 1.7 3.5": ["mediates"], "6.3 0.8 15.5": ["forgone"], "1.0 10.2 5.1": ["regressing"], "-1.5 0.5 8.0": ["primers"], "-1.4 3.7 8.7": ["hydroelectricity"], "3.6 7.3 12.8": ["homebrew"], "0.7 2.6 -6.2": ["congratulation"], "-0.2 4.9 0.6": ["counterfeited"], "9.9 6.5 6.9": ["unzipped"], "-6.4 8.3 3.4": ["rheumatology"], "-3.1 4.3 5.8": ["misapplied"], "-1.1 0.4 3.9": ["regale"], "7.3 8.1 3.6": ["bifurcated"], "10.7 14.2 0.7": ["coveting"], "-4.5 19.4 8.9": ["elector"], "-6.1 1.4 5.1": ["overbuilding"], "2.6 22.3 3.8": ["hilltops"], "6.8 18.6 15.1": ["colorblind"], "-1.9 -0.2 2.4": ["cosponsor"], "0.0 3.5 11.3": ["refinishing"], "13.6 1.9 5.6": ["locators"], "24.1 14.0 11.5": ["diorama"], "9.2 12.4 11.5": ["umm"], "-1.0 8.8 13.7": ["stratification"], "3.6 24.4 4.5": ["bomblets"], "22.6 12.7 20.0": ["oblong"], "11.5 14.3 19.5": ["vise"], "10.4 11.9 4.2": ["exulted"], "-14.6 3.4 20.0": ["durum"], "9.7 4.2 9.5": ["presaged"], "-0.4 12.4 4.5": ["brinksmanship"], "11.8 15.4 18.8": ["spreader"], "13.5 4.6 24.7": ["marbled"], "13.1 12.6 2.7": ["fairytales"], "6.2 7.6 18.2": ["sapling"], "1.8 8.3 1.6": ["collation"], "6.1 8.2 0.2": ["subcategories"], "-6.1 5.8 -6.2": ["exonerating"], "-4.5 10.4 9.6": ["lagers"], "-1.8 9.4 9.2": ["estimable"], "1.7 6.7 8.9": ["connotes"], "19.9 4.6 23.1": ["stork"], "6.2 14.8 14.2": ["lefthanded"], "12.0 8.4 4.4": ["deconstructing"], "7.3 -5.8 11.8": ["miniskirt"], "7.0 4.7 4.3": ["reciprocating"], "1.1 9.0 -0.3": ["urgings"], "-0.6 7.0 11.5": ["rueful"], "2.2 3.5 4.4": ["medicos"], "13.0 -7.6 6.3": ["doo"], "-4.9 5.4 4.1": ["freestyles"], "-0.6 5.6 13.1": ["accessorize"], "6.7 6.1 5.4": ["underinvestment"], "0.8 9.3 8.0": ["adaption"], "8.2 13.2 0.6": ["ridicules"], "5.4 13.9 11.4": ["tailbone"], "-9.9 2.8 -0.8": ["resection"], "0.4 12.7 36.7": ["sheepshead"], "-7.2 4.0 8.3": ["nonemergency"], "10.3 24.4 10.0": ["trope"], "11.9 4.9 14.2": ["plucks"], "8.9 31.5 -0.8": ["strafed"], "-1.0 9.9 3.0": ["institutionalizing"], "1.5 2.2 4.1": ["kilovolt"], "8.6 9.5 18.9": ["sledge"], "3.9 -2.6 6.1": ["typify"], "-1.1 2.6 6.1": ["overbuilt"], "-3.7 3.8 6.7": ["tangents"], "10.1 12.0 10.0": ["serfs"], "1.5 8.8 54.9": ["cobia"], "0.4 3.6 8.2": ["loadings"], "9.6 12.2 10.7": ["pitifully"], "11.9 0.7 -3.6": ["offical"], "2.7 6.6 -1.0": ["bibles"], "0.7 3.0 1.5": ["grumblings"], "18.0 4.0 3.5": ["foldable"], "14.2 2.3 7.9": ["scaffolds"], "21.7 4.1 10.8": ["schoolkids"], "-1.8 15.0 9.4": ["chauvinistic"], "-1.5 24.4 5.1": ["viscerally"], "-7.0 10.0 -2.1": ["informations"], "2.6 10.0 8.1": ["reboots"], "-0.4 8.8 12.9": ["flossing"], "-7.2 0.1 3.1": ["urologists"], "7.4 8.8 5.2": ["resizing"], "3.3 1.1 6.6": ["mingles"], "6.2 9.6 11.4": ["collie"], "9.2 12.8 4.7": ["tramples"], "-3.5 15.3 8.0": ["homeschoolers"], "9.6 4.5 5.8": ["leadup"], "3.8 8.4 5.4": ["unprintable"], "4.3 19.4 1.4": ["unashamed"], "16.9 7.3 7.4": ["metropolises"], "-7.8 9.1 10.4": ["iftar"], "4.8 6.8 14.8": ["toxics"], "0.4 12.9 -0.2": ["antihistamine"], "-11.7 16.3 -2.3": ["debriefed"], "-7.3 9.4 6.8": ["floodway"], "2.1 4.5 -0.4": ["haemorrhaging"], "1.6 8.3 9.3": ["overqualified"], "-3.7 2.5 9.5": ["lapper"], "3.4 13.2 19.6": ["variegated"], "4.5 3.9 -1.2": ["perforation"], "0.2 1.8 -1.3": ["vide"], "1.6 3.0 5.2": ["certifiable"], "0.9 7.7 21.4": ["solstice"], "2.8 2.5 7.3": ["tracksuits"], "5.4 10.8 -0.4": ["imager"], "4.2 6.2 8.3": ["worksites"], "19.4 9.5 21.7": ["chipmunks"], "10.6 4.2 14.3": ["peachy"], "16.1 17.9 3.9": ["infinitesimal"], "6.8 1.9 15.0": ["woodsy"], "4.6 2.4 6.8": ["rectal"], "6.8 1.9 8.0": ["giggly"], "-1.5 11.9 10.3": ["soliloquy"], "-0.9 11.1 5.8": ["parables"], "7.4 2.9 6.5": ["thickens"], "6.3 1.9 6.6": ["liveliest"], "6.4 12.3 6.0": ["machineries"], "1.2 1.2 13.7": ["forceps"], "3.5 -1.2 4.0": ["undelivered"], "10.8 9.9 13.2": ["antidumping"], "-4.7 3.8 -1.2": ["underplayed"], "2.5 5.2 21.5": ["tbsp"], "6.6 27.0 2.6": ["incapacitate"], "0.3 15.9 16.5": ["riverine"], "-2.7 11.4 13.8": ["narrowband"], "6.4 5.1 2.8": ["arounds"], "10.8 20.9 1.9": ["triumphalism"], "-1.8 8.0 12.8": ["sacramental"], "-4.7 15.4 10.7": ["noncitizens"], "10.2 25.0 15.9": ["underling"], "2.2 34.5 7.6": ["strafing"], "-1.6 6.4 12.8": ["conjugal"], "-2.6 -1.5 3.2": ["amateurism"], "2.4 7.9 3.9": ["cringes"], "9.5 16.2 17.2": ["shipwrecked"], "2.3 10.9 3.2": ["capillaries"], "-5.2 4.1 -2.3": ["redressed"], "0.1 7.1 13.2": ["cask"], "2.1 5.8 14.6": ["doosra"], "8.2 5.2 0.0": ["reinvents"], "3.5 4.8 6.1": ["telecommute"], "18.2 3.9 15.9": ["gondolas"], "2.5 1.9 16.2": ["hydroponic"], "10.2 5.9 12.5": ["smokin"], "3.3 9.5 8.8": ["crypto"], "8.5 15.3 17.3": ["rouge"], "11.7 4.7 11.4": ["stretchy"], "0.8 -3.4 -5.8": ["accredit"], "-5.9 7.2 7.1": ["crankshaft"], "6.7 11.7 14.2": ["flashers"], "-3.8 2.4 14.8": ["crudes"], "5.0 3.8 11.4": ["taxicabs"], "-9.0 13.8 1.7": ["effectuate"], "14.3 9.3 23.7": ["gyro"], "-5.4 3.9 5.3": ["bandwidths"], "7.0 12.6 11.2": ["lepers"], "11.5 17.8 4.5": ["groveling"], "1.5 3.8 -3.5": ["encrypts"], "8.0 9.9 9.1": ["fags"], "3.6 11.7 9.4": ["degenerates"], "6.9 6.0 10.3": ["beagles"], "-4.6 20.7 5.6": ["vindictiveness"], "9.6 -0.3 14.8": ["asian"], "-2.7 11.4 5.4": ["holeshot"], "7.3 8.4 8.7": ["preorders"], "5.1 13.3 -0.6": ["damnation"], "19.2 18.8 18.2": ["reptilian"], "3.3 8.4 11.8": ["procreate"], "2.1 9.6 3.0": ["wingback"], "22.4 10.8 11.7": ["hexagonal"], "7.7 10.0 3.2": ["transverse"], "7.3 -4.7 6.8": ["ce"], "-6.7 -1.9 5.7": ["stillbirths"], "-3.3 8.6 9.0": ["inactives"], "4.6 6.8 5.2": ["peerage"], "6.8 5.4 12.8": ["wizened"], "-5.1 2.3 6.0": ["conveyancing"], "8.8 17.3 3.6": ["exploitable"], "-7.4 8.3 -1.6": ["electrochemical"], "34.7 2.2 2.3": ["magnates"], "0.1 10.9 1.1": ["demoting"], "8.1 6.2 38.9": ["tempura"], "-7.9 7.3 -13.0": ["disseminates"], "-5.8 13.7 -5.0": ["deposing"], "-1.7 6.0 2.9": ["prurient"], "6.6 -1.3 14.0": ["bustier"], "3.2 6.8 3.9": ["rearrangement"], "4.3 10.4 -6.0": ["shied"], "2.6 13.3 7.1": ["rationalizations"], "14.0 4.6 8.1": ["sinewy"], "13.9 5.6 21.4": ["poppers"], "1.4 1.1 5.7": ["megabits"], "5.9 8.2 40.6": ["leek"], "1.9 -5.1 -0.3": ["cv"], "0.7 17.7 13.1": ["multipliers"], "-6.8 -1.3 12.0": ["leachate"], "10.2 0.8 -2.2": ["revolutionizes"], "-5.4 9.0 1.4": ["anticorruption"], "9.1 21.1 10.1": ["unthinking"], "-7.5 6.5 2.2": ["jotting"], "-2.3 -2.0 3.5": ["reproducibility"], "-3.6 3.6 16.7": ["spooned"], "10.3 5.9 -3.5": ["patentable"], "-8.8 8.2 2.6": ["chemistries"], "6.2 6.0 5.8": ["juxtaposes"], "-1.1 12.1 3.1": ["reestablishing"], "-0.4 7.9 7.1": ["reinterpret"], "-2.8 2.1 1.1": ["parallelism"], "8.4 1.9 8.7": ["bb"], "-9.2 13.0 1.5": ["dilated"], "3.8 2.1 4.0": ["damming", "xfs"], "6.0 5.5 11.4": ["aloha"], "18.9 12.9 16.6": ["hobbit"], "6.9 -3.4 5.6": ["stringently"], "-9.7 20.6 -1.1": ["maintainers"], "-0.2 1.3 9.3": ["bariatric"], "4.8 -0.6 -0.2": ["europe"], "-4.5 16.3 5.7": ["disinflation"], "10.4 -0.6 3.9": ["commerical"], "5.5 21.2 22.7": ["midges"], "-1.8 6.3 22.9": ["airboat"], "1.3 -2.4 7.6": ["nutraceuticals"], "0.1 11.7 3.2": ["renomination"], "9.9 10.6 1.4": ["demolishes"], "0.0 14.0 3.7": ["coz"], "-2.0 3.8 5.0": ["judicially", "discussable"], "-2.4 18.5 6.9": ["extrication"], "9.0 9.6 3.1": ["knowhow"], "-3.2 7.0 7.0": ["couponing"], "17.4 9.7 6.1": ["encircles"], "5.4 12.2 7.6": ["neutrinos"], "-2.6 19.9 8.8": ["definable"], "6.2 8.9 26.3": ["petunias"], "-0.2 3.4 -1.4": ["starstruck"], "5.3 7.1 13.9": ["sparkler"], "3.5 8.4 0.7": ["micrometers"], "-8.4 10.5 3.5": ["cinematographers"], "-4.8 6.4 3.4": ["audiophile"], "9.4 3.5 8.2": ["spoilsport"], "17.1 3.2 22.5": ["foamy"], "13.0 11.7 15.1": ["cocoons"], "1.9 9.6 6.5": ["confounds"], "11.0 7.0 10.0": ["zen"], "9.8 10.1 3.6": ["airbrush"], "2.1 -0.7 11.2": ["lute"], "4.3 11.1 2.2": ["cosmonaut"], "-5.0 8.0 10.9": ["sulphides"], "-3.4 3.1 2.3": ["quibbles"], "-4.3 30.3 0.7": ["homefront"], "12.7 5.6 11.9": ["extruded"], "3.1 -1.8 15.8": ["rockslide"], "6.1 12.7 3.6": ["smudges"], "17.4 5.7 12.9": ["hoary"], "-1.8 9.1 5.4": ["oversteer"], "0.3 14.5 8.2": ["sacredness"], "7.8 4.4 4.3": ["withstands"], "1.0 4.6 7.8": ["hearses"], "19.6 9.7 7.9": ["farts"], "8.8 3.2 17.8": ["poplar"], "17.6 10.9 2.5": ["footholds"], "-2.3 4.8 11.2": ["motorcoach"], "10.4 -0.3 12.5": ["suffixes"], "2.5 1.5 32.2": ["boneless"], "-6.2 -6.0 -3.9": ["inductions"], "3.8 13.4 8.7": ["unsportsmanlike"], "13.8 0.2 10.7": ["unicycle"], "3.1 -3.7 7.1": ["humidor"], "-3.2 7.8 5.2": ["inconveniencing"], "-2.7 4.9 12.2": ["rosaries"], "-1.0 10.2 0.7": ["decrypt"], "-0.9 0.1 3.8": ["biostatistics"], "3.7 4.9 4.8": ["shutoff"], "-3.4 8.6 15.7": ["claimer"], "12.4 12.8 8.1": ["mauls"], "-1.5 2.3 1.0": ["leafing"], "-1.6 8.5 -0.3": ["nitpick"], "7.4 13.0 3.1": ["topographic"], "-2.6 4.0 5.7": ["remixing"], "10.8 7.5 10.8": ["mountainsides"], "10.9 19.3 3.7": ["crucify"], "-4.8 8.7 3.5": ["esp"], "-3.7 3.1 7.9": ["floodplains"], "-1.8 -0.7 7.9": ["destocking"], "13.5 11.4 16.4": ["cranium"], "26.8 14.1 18.6": ["turd"], "-1.2 18.3 1.8": ["uniter"], "5.5 7.0 5.2": ["bandannas"], "2.3 8.3 11.8": ["speakeasy"], "2.2 21.2 6.1": ["inviolable"], "1.3 7.7 4.9": ["metabolize"], "5.0 10.9 -5.2": ["unobtrusively"], "20.5 6.7 16.1": ["octagonal"], "10.3 7.9 9.5": ["knackered"], "3.2 6.7 32.0": ["guava"], "-3.9 3.1 5.9": ["hypothesize"], "12.0 10.3 7.1": ["lowball"], "2.7 9.9 6.7": ["sloganeering"], "-4.8 3.4 28.8": ["boated"], "12.4 8.0 -4.5": ["chancellery"], "3.9 4.0 -1.6": ["reprocess"], "4.1 18.9 10.9": ["ridgeline"], "2.4 12.0 13.5": ["seethed"], "-5.6 14.9 0.6": ["madrasa"], "12.7 12.4 1.6": ["conundrums"], "9.5 2.5 7.2": ["ro"], "5.8 2.3 -0.5": ["notepads"], "12.2 7.6 11.6": ["desultory"], "5.6 7.2 12.7": ["taupe"], "10.6 6.2 18.8": ["jester"], "-8.8 6.2 14.3": ["tonnages"], "14.3 7.8 15.0": ["laboriously"], "14.2 14.3 3.6": ["monumentally"], "-5.2 -2.6 -6.4": ["remunerated"], "15.7 2.9 7.6": ["daddies"], "19.1 12.0 12.4": ["prospector"], "-4.8 13.7 10.7": ["repartee"], "17.7 12.7 11.8": ["cackling"], "5.3 4.0 4.8": ["gallstones"], "4.7 0.8 9.4": ["aux"], "8.6 1.7 11.1": ["thumbprint"], "12.6 19.6 5.2": ["invisibly"], "-2.8 15.5 5.7": ["goalkicker"], "3.2 9.7 6.4": ["eroticism"], "5.6 14.8 -0.6": ["vigilantly"], "8.5 8.6 8.2": ["paywall"], "-5.2 4.7 12.5": ["pasteurization"], "-9.0 1.9 2.0": ["decisioned"], "14.5 5.8 20.4": ["jackhammer"], "12.4 16.7 9.8": ["wreaking"], "11.2 12.7 6.1": ["savannah"], "-2.2 5.3 6.6": ["payee"], "5.6 0.3 9.0": ["pantsuit"], "9.1 -3.6 9.6": ["bod"], "6.5 8.9 7.8": ["inarticulate", "palmistry"], "13.9 9.7 11.2": ["droop"], "7.2 15.0 9.7": ["proclivities"], "-0.6 1.5 4.6": ["overbooked", "muvee"], "-4.7 13.6 -1.5": ["misrepresents"], "-5.2 4.2 7.8": ["laparoscopic"], "-11.8 5.3 20.9": ["marinades"], "-8.3 7.1 11.6": ["oscilloscope"], "7.3 16.0 8.0": ["malcontent"], "12.9 5.4 7.8": ["homogenized"], "6.8 20.4 0.1": ["gallantly"], "18.6 8.0 22.7": ["globs"], "8.2 15.8 7.7": ["irresistibly"], "6.9 15.6 6.8": ["extortionists"], "0.8 1.1 38.1": ["pancetta"], "10.8 4.4 6.8": ["knapsack"], "-0.7 2.7 11.1": ["retainers"], "10.1 12.5 2.0": ["indelibly"], "10.0 13.0 6.2": ["mindshare"], "-4.7 -5.9 -3.0": ["gerontology"], "1.4 7.0 5.6": ["reverential"], "10.5 4.9 3.9": ["headstart"], "0.2 11.5 4.0": ["stanzas"], "9.4 13.0 -0.9": ["crackles"], "1.9 5.6 18.7": ["canoeists"], "7.2 11.6 21.8": ["violets"], "12.7 8.8 8.2": ["eyeful"], "8.9 13.6 19.9": ["thistle"], "3.3 5.0 9.7": ["lengthens"], "-6.1 2.1 8.7": ["clavicle"], "-7.3 -5.8 12.5": ["paratransit"], "1.6 6.8 7.2": ["redecorate"], "4.8 2.3 16.0": ["parklands"], "3.3 22.0 3.6": ["unbending"], "2.6 9.0 9.4": ["coalfields"], "17.5 10.5 9.8": ["clanking"], "9.7 2.4 0.6": ["compulsorily"], "3.1 1.1 14.5": ["econ"], "-2.2 7.8 -1.7": ["reactivity"], "0.9 4.7 6.1": ["annotate"], "4.3 9.5 14.2": ["nodules"], "10.1 4.3 7.3": ["wagged"], "6.6 3.9 0.1": ["reclined"], "7.2 1.9 8.7": ["mtpa"], "6.9 2.7 11.5": ["scrotum"], "21.3 5.2 18.9": ["pixie"], "-0.4 2.4 5.5": ["headend"], "6.6 13.5 6.9": ["smooching", "headlocked"], "-2.5 -0.3 9.2": ["mephedrone"], "1.5 2.6 6.1": ["hitchhiked"], "-1.5 -3.4 3.3": ["proofreading"], "9.1 16.8 5.8": ["trickster"], "-1.8 5.3 -0.2": ["dalliances"], "9.6 14.7 4.7": ["capitulating"], "-18.3 10.1 11.4": ["remarriage"], "-0.2 1.1 14.2": ["refi"], "5.7 3.1 6.3": ["hooter"], "8.8 10.0 17.4": ["regrow"], "10.5 18.7 11.9": ["entropy"], "-6.0 -2.3 7.3": ["expedites"], "10.4 15.6 16.3": ["petal"], "18.6 6.5 56.4": ["crustacean"], "3.2 14.7 -1.4": ["gendarmes"], "9.6 8.3 11.9": ["goodie"], "9.8 5.1 3.8": ["constriction"], "7.0 2.7 8.2": ["beaned"], "6.7 2.5 5.9": ["harps"], "0.8 1.4 5.2": ["lipsticks"], "8.7 13.4 26.7": ["retriever"], "6.7 13.7 8.9": ["iconoclast"], "6.3 -1.4 12.6": ["banknote"], "-9.1 26.2 3.4": ["neutralization"], "11.9 15.1 10.4": ["knuckleheads"], "10.2 -0.5 -0.4": ["timekeeping"], "-5.1 2.5 8.6": ["duplications"], "1.9 14.6 6.2": ["looses"], "-7.8 -1.5 -4.2": ["coauthored"], "18.4 13.7 14.5": ["chomp"], "9.2 15.3 6.3": ["redoubling"], "4.8 19.4 -3.3": ["lionized"], "0.9 1.7 13.7": ["godowns"], "4.8 2.8 4.4": ["brawled"], "9.0 -3.9 9.1": ["fetes"], "1.5 2.9 11.8": ["microchipped"], "3.6 4.3 30.5": ["pate"], "0.1 -1.3 13.1": ["ponytails"], "1.3 3.6 21.3": ["roasters"], "11.8 -6.9 7.5": ["torcetrapib"], "-4.7 7.3 1.4": ["psychoanalyst"], "6.6 14.4 5.1": ["warders"], "10.8 9.4 13.5": ["clubby"], "9.4 11.1 3.5": ["capillary"], "13.8 9.7 9.2": ["sneezed"], "3.2 5.8 25.6": ["crabby"], "2.0 6.7 -6.4": ["photocall"], "13.5 23.8 37.0": ["harpoon"], "2.4 13.4 41.7": ["cormorants"], "5.9 16.8 28.2": ["bobber"], "13.1 21.1 5.7": ["infest"], "7.7 7.4 11.3": ["darkens"], "2.1 6.5 22.8": ["fresco"], "7.5 6.8 16.5": ["arrowheads"], "-0.7 4.9 11.9": ["botanicals"], "15.5 25.1 8.2": ["madmen"], "5.2 14.0 12.2": ["chromite"], "-2.5 3.5 6.5": ["reminiscence"], "9.5 6.5 0.3": ["aping"], "2.5 10.2 -1.5": ["inefficiently"], "5.9 6.5 3.0": ["flirtations"], "6.4 0.9 2.7": ["ter"], "-7.9 1.1 -4.1": ["glosses"], "15.0 12.1 9.0": ["imperceptible"], "10.2 14.1 18.9": ["arbor"], "0.0 8.3 3.0": ["technocratic"], "2.8 19.7 7.1": ["misplay"], "-2.1 16.7 7.0": ["insincerity"], "10.3 9.9 15.9": ["husks"], "4.8 3.5 9.7": ["untraditional"], "9.0 9.7 8.4": ["chirps"], "5.1 7.5 4.3": ["watchmaker"], "-6.1 15.1 -4.4": ["recce"], "8.4 12.8 14.6": ["herdsmen"], "3.1 10.0 10.2": ["prudish"], "-1.4 7.5 20.6": ["uplands"], "-4.2 2.6 5.6": ["recitations"], "-3.1 12.2 7.1": ["overplaying"], "13.0 3.7 8.1": ["loos"], "-6.3 7.8 5.1": ["orthopedist"], "11.6 17.1 5.7": ["defecating"], "8.0 7.8 8.6": ["loftier"], "-3.8 22.0 2.9": ["acolyte"], "20.4 4.3 14.3": ["brained"], "14.7 13.0 27.3": ["crocs"], "-3.8 1.9 5.8": ["microbicide"], "14.3 11.9 11.7": ["reveler"], "9.8 12.1 17.7": ["marigolds"], "1.7 6.8 10.9": ["microbrewery"], "12.0 8.0 4.7": ["lovefest"], "28.6 16.3 4.5": ["juggernauts"], "21.1 4.6 10.6": ["scraper"], "6.7 6.8 4.4": ["grindstone"], "1.1 -2.1 3.4": ["peripatetic"], "-14.5 0.9 4.1": ["rabbinic"], "21.2 -5.2 11.3": ["spools"], "8.0 12.0 20.3": ["gyros"], "13.5 4.4 12.4": ["frolicked"], "7.5 0.5 27.2": ["lemongrass"], "5.8 -1.5 39.2": ["taro"], "-4.6 0.7 9.9": ["rootsy"], "6.5 3.2 13.7": ["infra"], "5.7 1.6 -1.1": ["interpretative"], "0.0 4.4 0.7": ["edifying"], "13.0 8.7 11.0": ["stowaway"], "4.1 9.3 4.9": ["reshuffles"], "-4.4 4.7 11.3": ["totesport"], "4.5 14.3 10.4": ["rappel"], "3.5 12.2 7.1": ["dampness"], "17.6 17.5 9.4": ["wastelands"], "7.8 9.5 4.6": ["adeptly"], "11.9 -0.8 -2.3": ["screensavers"], "0.8 14.4 5.9": ["topographical"], "0.5 0.8 13.3": ["refinished"], "5.2 1.8 3.6": ["ballfields"], "-1.5 6.4 22.1": ["baccarat"], "6.8 3.3 4.5": ["cashflows"], "14.7 11.8 1.9": ["slink"], "2.1 6.3 10.3": ["lowlights"], "3.6 8.5 9.9": ["regurgitate"], "-3.1 16.9 4.6": ["ghosting"], "-3.8 29.1 8.2": ["pacifists"], "19.2 11.5 2.6": ["telescopic"], "7.5 20.6 4.3": ["infiltrates"], "-1.2 -0.4 7.0": ["orthotics"], "9.7 7.4 5.4": ["decouple"], "11.2 6.5 6.2": ["nebula"], "-3.8 16.8 8.6": ["moneylenders"], "18.9 2.3 8.1": ["sculptured"], "9.8 6.3 2.9": ["starker"], "4.7 11.7 11.2": ["imperils"], "21.2 7.5 14.9": ["confectioner"], "-4.2 3.7 3.0": ["genealogists"], "-2.4 11.1 13.5": ["cargos"], "11.5 12.7 5.1": ["timidly"], "5.2 6.7 3.0": ["luminosity"], "0.1 18.1 2.3": ["disliking"], "-3.1 12.2 9.7": ["libertarianism"], "1.6 10.7 15.2": ["openside"], "-1.4 5.0 13.4": ["modifieds"], "10.9 10.5 10.3": ["insulators"], "-4.0 8.8 0.3": ["competences"], "8.2 3.8 10.9": ["schoolwide"], "12.6 6.8 8.5": ["proportioned"], "10.2 25.9 5.2": ["obliteration"], "9.8 19.2 6.0": ["singularity"], "-8.9 10.7 -3.7": ["inculcated"], "5.5 4.2 4.5": ["spigots"], "8.9 13.9 8.2": ["gorges"], "-0.7 7.6 0.6": ["telesales"], "3.3 13.0 -0.3": ["ironical"], "0.4 4.7 49.6": ["yellowtail"], "5.5 8.7 14.9": ["atolls"], "2.4 3.1 4.4": ["bantered"], "-4.1 9.0 7.2": ["chlorination"], "3.2 22.6 8.8": ["wreckers"], "23.9 3.2 17.5": ["conical"], "12.5 -0.2 14.9": ["ono"], "11.1 14.3 5.4": ["hyphen"], "-8.3 11.2 5.0": ["incivility"], "-0.7 3.5 4.6": ["securityholders"], "3.1 4.6 10.3": ["chargeback"], "-3.8 5.6 19.0": ["racinos"], "9.3 10.8 55.6": ["mollusks"], "1.2 5.7 2.2": ["redecorated"], "9.7 12.2 12.3": ["yelp"], "-6.2 2.2 2.5": ["concertos"], "-2.8 4.3 0.5": ["videophone"], "5.5 11.2 3.5": ["disperses"], "-9.0 2.4 12.6": ["veneers"], "4.3 8.8 4.6": ["outgo"], "0.9 16.2 10.4": ["conceited"], "-1.4 6.0 9.5": ["bunching"], "3.7 6.6 0.7": ["newsmaker"], "17.7 5.1 10.9": ["robed"], "6.5 -2.5 8.5": ["midcentury"], "0.7 2.7 12.4": ["bran"], "4.3 -0.0 5.9": ["craned"], "10.0 2.6 10.1": ["underpriced"], "11.7 4.9 16.7": ["lilt"], "-1.2 6.8 8.8": ["taints"], "3.0 13.3 8.2": ["fencer"], "2.7 10.1 2.4": ["ultraportable"], "-1.6 5.6 -2.7": ["physiologic"], "-2.6 0.1 0.2": ["refinances"], "7.4 2.7 16.8": ["futon"], "0.9 3.6 4.9": ["flunking"], "5.5 13.6 6.2": ["intensities"], "5.8 7.4 4.0": ["cantered"], "-0.8 20.2 4.9": ["peacefulness"], "1.7 3.2 9.8": ["bhangra"], "-9.6 5.8 5.0": ["instrumentalist"], "-11.4 8.5 2.1": ["reoccurrence"], "12.5 5.2 11.3": ["cantilever"], "11.9 0.5 9.6": ["hotcakes"], "9.8 26.3 -0.5": ["counteroffensive"], "12.1 5.2 6.6": ["whiteout"], "2.9 13.6 1.3": ["bloodhounds"], "-2.9 24.9 6.1": ["rightness"], "0.6 9.1 8.8": ["abutters"], "-0.0 13.1 2.5": ["inaccessibility"], "2.3 3.7 9.8": ["cortical"], "11.1 11.0 8.9": ["disentangle"], "0.3 -5.0 -0.6": ["cancelation"], "-14.8 5.8 -0.6": ["exacerbation"], "0.3 4.9 7.1": ["curtails"], "20.8 18.2 13.8": ["amoeba"], "-4.3 6.4 1.1": ["hatchbacks"], "5.6 9.9 8.5": ["overachievers"], "7.2 16.1 1.7": ["outdoing"], "6.3 6.8 11.6": ["tannery"], "12.5 3.4 21.2": ["tabby"], "16.7 9.2 9.1": ["junky"], "-3.3 9.6 3.5": ["airspeed"], "1.9 0.9 -6.5": ["nr"], "-0.6 12.9 4.2": ["cherishing"], "2.4 17.2 6.0": ["dispassionately"], "-6.1 8.4 12.3": ["mortgagee"], "6.5 4.5 8.9": ["disconsolate"], "-5.0 13.6 6.3": ["robocalls"], "4.8 -2.8 2.6": ["warehoused"], "7.8 0.4 4.5": ["clothier"], "-10.3 16.1 3.7": ["briefer"], "10.2 21.5 6.4": ["innermost"], "2.4 0.3 6.0": ["databank"], "-0.8 7.3 13.8": ["stovetop"], "-0.2 10.7 8.6": ["fission"], "8.2 16.2 7.0": ["rejoices"], "11.9 1.2 3.9": ["sqft"], "3.6 9.9 9.1": ["breezeway"], "-7.9 4.8 5.3": ["lymphedema"], "12.6 14.8 14.5": ["chariots"], "7.4 13.3 10.3": ["disorientated"], "7.6 21.3 3.0": ["fealty"], "-0.1 2.3 2.7": ["rota"], "0.5 16.6 7.7": ["moviegoer"], "1.5 1.3 11.8": ["lac"], "12.3 3.0 12.1": ["coo", "plummetted"], "14.0 12.7 3.6": ["noone"], "0.7 5.9 6.3": ["suboptimal"], "22.1 35.6 14.1": ["marauders"], "-0.6 -1.5 6.3": ["chauffeurs"], "-1.9 14.5 -2.2": ["misleads"], "3.6 18.5 5.7": ["unerring"], "20.1 8.5 12.2": ["presto"], "17.1 16.5 9.1": ["hurtle"], "-1.7 12.8 17.8": ["skeet"], "11.2 10.6 7.7": ["fixers"], "-8.4 -1.8 6.2": ["rehabs"], "-1.4 10.1 9.6": ["penury"], "3.8 3.6 12.8": ["mambo"], "13.2 2.0 21.4": ["toboggan"], "7.9 2.7 6.1": ["sillier"], "8.2 6.8 6.2": ["risible"], "-6.4 15.0 4.7": ["biblically"], "2.9 1.5 -2.6": ["impel"], "0.5 10.1 6.6": ["piecing"], "9.1 5.8 7.9": ["paralleling"], "9.6 12.5 9.3": ["stashes"], "7.0 6.7 6.5": ["timekeeper"], "-3.4 -1.7 9.3": ["megalitres"], "5.0 21.2 10.3": ["brutalizing"], "12.7 10.0 13.7": ["scavenger"], "7.6 13.5 2.7": ["indistinct"], "-5.3 -1.5 11.5": ["microarrays"], "3.8 21.8 6.9": ["rightists"], "-2.1 2.8 24.6": ["houseboats"], "15.1 10.4 3.6": ["infront"], "11.6 6.4 1.7": ["didgeridoo"], "-6.4 -0.2 10.3": ["hemlines"], "6.1 5.4 1.9": ["optician"], "6.0 6.7 9.2": ["minting"], "9.2 3.2 8.6": ["regurgitated"], "5.3 -3.5 1.6": ["shoehorn"], "11.9 3.9 11.7": ["mon"], "0.0 10.6 5.7": ["impelled"], "13.3 0.9 7.8": ["aahs"], "-14.4 2.4 1.4": ["perioperative"], "1.8 12.1 -2.1": ["phonetic"], "-10.1 12.8 9.7": ["upperclassman"], "-0.4 6.2 9.1": ["lookers"], "-7.0 -0.7 -0.0": ["sleepwear"], "0.4 18.9 7.1": ["predicate"], "2.6 8.9 3.8": ["congruent"], "7.3 9.8 12.3": ["racecourses"], "3.4 6.5 25.2": ["latkes"], "9.0 21.4 1.6": ["terrifies"], "11.1 6.1 16.7": ["derriere"], "-1.1 16.2 7.3": ["abhorrence"], "15.0 9.4 11.0": ["pinstriped"], "2.6 6.9 10.8": ["ingenue"], "-0.2 9.2 0.4": ["encumbrances"], "11.9 12.2 10.3": ["exuberantly"], "-12.5 5.0 21.8": ["syrah"], "25.9 13.2 24.6": ["horned"], "1.8 6.5 0.3": ["procures"], "18.9 11.7 9.4": ["savant"], "1.1 13.4 7.1": ["cussed"], "-2.8 26.3 -5.5": ["brutalities"], "3.6 7.8 1.6": ["juxtaposing"], "4.7 2.5 23.9": ["cantaloupes"], "-3.0 8.6 9.6": ["glioma"], "-0.1 9.6 10.4": ["catechism"], "-14.2 0.1 4.6": ["perinatal"], "18.5 11.1 10.7": ["sheathed"], "3.9 9.8 9.4": ["druthers"], "7.5 16.8 10.6": ["queers"], "0.3 7.4 7.6": ["parter"], "-4.5 -0.4 8.7": ["haj"], "7.2 2.1 10.6": ["highrise"], "5.1 7.3 5.9": ["mesa"], "26.7 7.0 19.1": ["tendrils"], "1.7 5.3 0.1": ["bassinet"], "-4.8 3.6 19.4": ["snowboardcross"], "4.8 8.0 8.2": ["hauntingly"], "2.9 23.7 3.5": ["adventurism"], "0.3 -2.0 -6.2": ["ventricular"], "0.7 18.3 4.0": ["graver"], "6.9 -0.7 0.8": ["shortlists"], "8.3 8.8 7.8": ["tableaux"], "-0.2 14.0 6.7": ["incoherence"], "1.9 5.9 2.1": ["biophysics"], "-5.2 10.9 2.3": ["unsparing"], "1.8 1.0 6.2": ["hooky"], "21.2 17.0 0.2": ["mightier"], "-0.1 0.6 6.4": ["booker"], "-4.6 7.8 -1.4": ["striven"], "17.0 20.0 1.0": ["incinerate"], "4.7 10.5 29.2": ["jigging"], "2.4 6.4 4.5": ["cannibalization"], "-10.4 0.2 5.2": ["casework"], "2.1 7.3 33.7": ["tarragon"], "2.5 9.1 3.4": ["drafty"], "12.1 17.4 33.3": ["larva"], "-5.0 1.9 14.3": ["ep"], "3.7 4.6 8.8": ["dinger"], "10.0 13.5 23.6": ["magnolia"], "-6.2 19.5 1.3": ["unreservedly"], "-2.8 19.0 39.5": ["muskie"], "15.6 5.5 4.7": ["thorniest"], "17.4 1.8 7.8": ["swaddled"], "5.9 3.4 6.8": ["showjumping"], "-8.3 -0.6 3.8": ["rebooked"], "-3.2 -6.3 12.2": ["albumin"], "-6.3 -2.9 -3.8": ["transcriptions"], "7.4 15.6 8.5": ["feudalism"], "1.2 3.0 11.8": ["virginal"], "6.7 14.8 6.8": ["benighted"], "0.5 7.1 10.5": ["remunerative"], "-2.3 -2.5 3.8": ["returnable"], "-0.5 6.3 31.6": ["bruschetta"], "5.3 15.8 4.0": ["entrap"], "13.5 12.9 5.5": ["crazily"], "6.7 3.6 6.1": ["costumers"], "-1.0 2.8 0.4": ["rtd"], "13.6 -0.3 7.2": ["waif"], "6.2 -0.4 10.1": ["transvestites"], "7.0 3.0 12.3": ["containerboard"], "11.9 3.7 2.6": ["tickers"], "-1.5 6.1 5.7": ["driveline"], "-6.9 10.2 6.1": ["potable"], "9.5 14.6 31.2": ["stingrays"], "-6.8 9.0 12.8": ["lambing"], "5.0 9.3 11.9": ["poetically"], "-2.6 15.9 -2.3": ["encamped"], "1.8 7.3 14.3": ["nightgown"], "0.2 13.0 1.6": ["excusable"], "-4.3 3.5 6.3": ["charring"], "2.3 26.6 13.3": ["militarist"], "3.5 11.1 3.5": ["misconceived"], "5.6 24.0 11.1": ["obstructionists"], "-2.2 0.9 -2.2": ["layperson"], "8.7 -0.5 -0.5": ["dlrs"], "6.0 4.6 8.3": ["cranial"], "0.5 -9.9 -2.8": ["notaries"], "2.1 15.0 13.4": ["prognostication"], "15.2 7.8 5.3": ["clickable"], "10.8 22.0 3.2": ["unimaginably"], "1.3 -2.6 3.9": ["acetate"], "10.1 -0.0 6.5": ["slipshod"], "12.1 6.3 12.7": ["latecomers"], "8.2 15.1 3.9": ["slouches"], "-0.8 7.3 5.9": ["afforestation"], "10.7 -0.4 5.5": ["debutantes"], "17.9 -1.4 6.2": ["reawakened"], "14.1 8.5 10.0": ["daredevils"], "0.3 6.0 1.2": ["relinquishes"], "-1.9 2.5 4.5": ["blurbs"], "2.4 5.6 3.9": ["strummed"], "0.7 -0.1 0.2": ["serialization"], "-2.6 8.1 3.7": ["reprimanding"], "11.7 8.5 1.4": ["contortions"], "12.6 9.8 6.6": ["panoramas"], "12.9 6.1 0.5": ["quadrillion"], "5.0 3.9 8.3": ["nudist"], "3.2 4.1 5.0": ["sft"], "13.3 13.5 12.7": ["tyke"], "-4.3 4.5 8.2": ["honeymooners"], "5.0 12.2 -3.5": ["electrostatic"], "9.7 3.8 15.9": ["colander"], "12.0 17.7 8.2": ["mafias"], "-0.4 29.4 4.1": ["naxalites"], "9.8 4.0 8.3": ["triptych"], "-4.0 8.6 1.9": ["inapplicable"], "4.8 12.3 16.1": ["moors"], "2.5 5.8 7.3": ["undocking"], "15.1 1.4 9.0": ["glitters"], "12.6 3.1 1.8": ["climbdown"], "-4.4 2.7 13.6": ["backwardation"], "-5.6 7.1 -11.3": ["retd"], "-1.8 5.4 9.3": ["runnings"], "-0.3 12.2 4.4": ["arbitrariness"], "4.1 3.0 6.1": ["wednesday"], "-2.2 5.4 -1.0": ["anesthetist"], "1.2 8.8 15.3": ["matting"], "0.3 5.7 13.8": ["brooks"], "23.8 1.6 13.5": ["encasing"], "10.1 4.8 -1.8": ["subsidization"], "7.1 2.3 7.8": ["schlock"], "18.6 6.0 8.6": ["passel"], "-6.2 1.4 7.0": ["rooming"], "-5.3 6.4 11.5": ["irinotecan"], "-3.1 4.0 2.5": ["hyperglycemia"], "0.9 5.2 11.9": ["inheritances"], "0.7 11.5 5.1": ["recombination"], "8.7 2.1 6.6": ["comforters"], "1.2 4.4 -5.5": ["absolving"], "9.4 22.4 19.8": ["caster"], "17.9 3.6 3.7": ["clipboards"], "0.1 1.8 9.2": ["leafed", "trazodone"], "8.7 9.4 3.0": ["snickers"], "10.0 3.0 -5.9": ["unflagging"], "-0.2 2.0 11.8": ["quintals"], "11.0 4.2 26.2": ["stringy"], "-1.1 15.0 11.1": ["rebalanced"], "0.0 -5.7 11.9": ["inlays"], "-4.4 3.2 5.0": ["cardiomyopathy"], "-5.0 5.6 4.8": ["acclimatization"], "-1.8 7.1 14.3": ["malnourishment"], "2.4 21.6 22.2": ["paintballs"], "10.3 3.3 17.5": ["breasted"], "-2.9 2.7 8.0": ["paragliding"], "5.9 16.7 17.8": ["backbreaker"], "11.4 16.7 6.7": ["kneels"], "9.2 8.1 7.2": ["planar"], "2.8 7.3 10.2": ["kiloliters"], "7.7 16.3 13.0": ["knucklehead"], "15.8 8.8 8.8": ["enviro"], "-2.1 6.8 23.2": ["succulents"], "3.2 4.4 -0.4": ["vacates"], "8.9 13.3 -0.7": ["sightlines"], "-1.7 5.0 29.2": ["boatyard"], "1.1 0.6 9.7": ["penciling"], "5.0 8.2 6.4": ["millennials"], "21.8 4.8 5.2": ["prance"], "-10.3 2.4 2.6": ["bequests"], "0.3 22.5 8.3": ["smirks"], "4.5 4.2 6.3": ["ny"], "9.2 6.1 9.8": ["steelworks"], "8.8 -1.3 6.7": ["twee"], "15.8 2.1 6.1": ["greasing"], "-3.7 8.3 10.4": ["microbiological"], "14.0 -0.0 15.4": ["pails"], "15.9 4.1 12.1": ["wisps"], "5.5 11.5 1.8": ["overactive"], "12.8 7.1 13.0": ["mauve"], "-7.8 2.1 21.6": ["ozs"], "10.5 6.6 13.1": ["slather"], "8.1 5.2 14.6": ["tenner"], "6.0 1.4 38.9": ["ceviche"], "12.1 17.3 6.3": ["lapdog"], "-1.6 11.6 2.8": ["hemorrhoids"], "0.5 -1.8 51.8": ["roe"], "11.9 19.6 12.1": ["perp"], "2.1 11.6 12.9": ["suddenness"], "-4.3 9.3 -0.6": ["xiii"], "2.7 12.2 11.1": ["tweener"], "4.0 18.5 5.3": ["emboldening"], "-0.2 6.4 6.6": ["endoscope"], "2.8 4.6 5.3": ["bollywood"], "9.0 12.3 -0.6": ["matchless"], "6.5 16.1 13.8": ["dems"], "2.0 13.0 7.7": ["devolves"], "1.5 4.3 3.6": ["tonsillitis"], "24.8 15.4 15.0": ["unicorns"], "0.9 16.1 7.3": ["eardrum"], "5.4 17.1 1.6": ["thirsting"], "6.4 5.8 26.3": ["baguettes"], "-2.0 5.7 4.1": ["sarpanch"], "5.8 10.4 10.4": ["squeegee"], "-12.1 6.0 3.4": ["abetment"], "-2.0 6.9 24.1": ["lilacs"], "4.4 4.8 24.3": ["dredges"], "-5.8 9.6 5.2": ["procedurally"], "1.0 18.1 -2.6": ["liberates"], "4.6 8.4 25.1": ["oceanographic"], "12.0 4.7 9.7": ["factoids"], "3.6 3.9 13.0": ["divvying"], "-2.3 -0.7 2.8": ["multicenter"], "5.1 21.6 14.2": ["nonlethal"], "17.4 20.8 12.5": ["slingshots"], "8.4 8.2 12.8": ["unsustainably"], "14.0 23.2 8.2": ["megalomaniac"], "-6.7 6.4 3.1": ["deejays"], "13.8 12.2 5.4": ["disintegrates"], "-7.4 -2.8 3.4": ["adjournments"], "14.3 4.2 4.7": ["moneymakers"], "10.9 7.7 10.0": ["ceremoniously"], "5.8 6.0 -0.3": ["conceptualize"], "5.1 4.6 7.0": ["nucleotides"], "-2.6 7.2 8.7": ["adjuncts"], "5.6 12.9 5.6": ["reordering"], "-5.2 15.2 -1.7": ["polemical"], "8.5 16.5 -3.7": ["entrenchment"], "8.2 6.6 29.5": ["incher"], "-1.0 3.9 4.5": ["shales"], "-4.5 -0.7 6.2": ["homocysteine"], "-0.1 4.3 14.5": ["uproarious"], "7.4 10.4 11.6": ["imprecision"], "9.6 6.9 1.5": ["misleadingly"], "-4.9 13.4 22.9": ["glazes"], "1.5 10.0 8.6": ["compassionately"], "-2.7 9.6 2.7": ["theorizing"], "7.6 3.4 10.0": ["clink"], "1.2 12.0 2.3": ["ferreting"], "-1.9 8.2 11.2": ["camerawork"], "5.0 11.5 8.9": ["broiling"], "13.3 11.2 5.0": ["soiling"], "1.9 23.7 -4.6": ["combated"], "6.6 7.0 12.5": ["neuroses"], "22.3 30.8 11.5": ["bazooka"], "5.9 10.5 8.1": ["fatuous"], "28.7 9.9 13.9": ["gobbles"], "3.3 6.9 0.1": ["overhearing"], "18.0 10.9 8.4": ["driverless"], "14.6 3.7 2.9": ["exceptionals"], "-1.9 -0.3 2.9": ["conditioners"], "-4.9 5.1 1.1": ["airworthiness"], "-5.6 16.7 0.5": ["disbelieve"], "6.1 8.3 15.1": ["strangles"], "10.5 10.0 13.9": ["purples"], "6.4 20.5 7.2": ["inwardly"], "-1.9 -3.8 5.6": ["kt"], "22.3 11.2 20.0": ["gluttonous"], "9.4 1.9 9.2": ["tethers"], "6.3 21.9 3.7": ["cyberattack"], "15.8 -5.4 2.3": ["shimmied"], "7.6 5.7 3.9": ["windbreaker"], "7.0 6.7 1.0": ["foretaste"], "11.5 9.4 14.5": ["teapots"], "6.2 -2.5 9.7": ["baggers"], "1.1 20.3 8.3": ["hatreds"], "-0.3 9.0 8.9": ["churchgoing"], "4.2 14.4 8.7": ["disassembly"], "7.0 10.9 18.8": ["mainsail"], "4.2 -0.7 4.4": ["bareback"], "-6.8 10.6 2.8": ["polygamists"], "3.9 5.2 10.2": ["waterpark"], "3.7 4.7 1.8": ["yesteryears"], "12.5 9.8 10.8": ["surrealistic"], "1.3 3.8 -0.1": ["lightheaded"], "2.3 3.9 5.4": ["lumen"], "5.7 5.2 11.7": ["busboy"], "9.0 6.7 15.1": ["yu"], "1.6 8.9 15.5": ["heatsink"], "2.4 14.2 -1.3": ["rebuking"], "-0.0 3.9 3.6": ["tastemakers"], "-0.4 5.7 -2.6": ["agonist"], "0.8 3.0 18.2": ["seaworthy"], "-3.1 1.0 21.0": ["microbreweries"], "8.2 9.3 12.6": ["intricacy"], "0.4 6.8 14.1": ["vintner"], "4.3 4.1 22.9": ["husbandry"], "9.0 12.5 3.9": ["unmasking"], "6.9 6.9 13.0": ["terriers"], "-2.0 10.8 4.5": ["unimpeachable"], "9.8 12.5 5.6": ["steadiest"], "3.7 8.3 9.6": ["parley"], "1.4 10.5 7.2": ["sump"], "2.1 4.2 -3.0": ["ventricle"], "8.4 12.4 7.1": ["incongruity"], "7.6 6.3 19.0": ["wellies"], "6.0 12.6 4.9": ["hyphenated"], "6.5 7.5 -0.5": ["nosebleeds"], "6.0 21.5 10.9": ["checkmate"], "-8.5 0.1 8.4": ["concurrency"], "-8.9 4.3 1.4": ["handwashing"], "-0.2 15.8 -0.3": ["subjectively"], "18.6 16.9 10.7": ["crossbones"], "11.9 11.2 7.7": ["chirped"], "-3.3 7.6 14.4": ["raga"], "10.5 -5.5 2.8": ["interims"], "-1.1 8.5 2.1": ["hattrick"], "7.6 4.8 -1.4": ["outcries"], "4.5 15.9 9.5": ["repellents"], "2.1 17.6 7.5": ["outcoached"], "-0.7 -0.9 2.6": ["bookers"], "-6.0 7.5 1.7": ["plainspoken"], "12.7 6.0 22.6": ["nettle"], "2.7 18.8 6.0": ["apocryphal"], "2.1 32.3 7.4": ["traitorous"], "9.5 10.1 23.4": ["croissant"], "2.5 26.9 7.5": ["heretic"], "-6.7 11.8 12.6": ["bootlegs"], "5.3 6.0 -4.7": ["chloroform"], "5.9 17.6 7.3": ["impassive"], "14.2 -4.7 6.3": ["una"], "3.1 -1.8 6.8": ["slapdash"], "-2.4 -1.0 5.2": ["uterine"], "1.5 5.3 -2.2": ["undervalue"], "6.7 9.9 12.7": ["nave"], "11.5 4.5 5.6": ["weirdos"], "7.9 24.2 2.6": ["terrifyingly"], "4.8 2.4 9.1": ["prohibitively"], "2.5 15.9 7.0": ["vacillating"], "-3.2 4.0 14.8": ["pawnshops"], "13.6 4.4 7.9": ["skybox"], "6.1 5.5 7.7": ["florid"], "13.6 4.8 4.9": ["convulsing"], "10.7 11.3 8.8": ["thickets"], "10.0 -1.1 -0.5": ["coursed"], "6.0 0.3 2.6": ["officals"], "0.6 6.1 18.7": ["superyacht"], "7.3 7.4 5.9": ["deductibility"], "3.3 10.8 5.6": ["sociopolitical"], "19.9 9.7 5.8": ["blocky"], "-7.2 4.9 5.6": ["etiology"], "-2.5 5.0 14.7": ["divorcees"], "13.4 -0.6 7.1": ["dkr"], "7.8 16.2 1.7": ["furtively"], "15.4 16.9 14.5": ["ergo"], "-10.9 2.7 7.2": ["nephrology"], "16.8 0.1 12.9": ["primo"], "16.7 15.3 26.8": ["opossum"], "6.1 11.0 7.8": ["synchronicity"], "11.3 29.4 12.2": ["lightsaber"], "-0.6 5.3 2.6": ["utilityman"], "0.8 0.6 4.5": ["sifts"], "6.8 6.1 4.5": ["halos"], "2.1 17.7 7.6": ["survivalist"], "0.2 19.0 6.9": ["wordsmith"], "17.9 10.4 9.6": ["pecked"], "14.1 3.1 3.5": ["stampedes"], "3.4 12.8 15.3": ["endearment"], "7.2 -8.0 4.6": ["cq"], "6.9 7.7 13.2": ["britches", "tenn"], "8.2 2.6 8.6": ["stockbroking"], "9.2 7.3 6.6": ["steelworker", "cranksets"], "7.9 -0.6 2.8": ["captioning"], "11.3 7.0 6.4": ["protrude"], "6.1 8.2 6.8": ["priestess"], "12.3 3.8 7.7": ["unmissable"], "-0.7 16.3 7.9": ["backbiting"], "-2.6 -1.6 29.0": ["loin"], "0.8 5.6 1.3": ["modafinil"], "-0.2 6.9 6.1": ["geochemistry"], "3.4 7.6 4.4": ["criminalizes"], "4.6 14.1 -2.3": ["truely"], "3.4 -2.9 0.1": ["mollified"], "3.9 0.9 12.0": ["unseasonably"], "14.3 14.7 11.4": ["marionette"], "-3.8 12.9 11.4": ["arable"], "3.9 8.8 3.2": ["parodying"], "7.3 5.9 2.1": ["ir"], "0.5 5.7 4.4": ["interceded"], "-1.1 6.1 -6.1": ["vindicating"], "4.3 20.5 4.5": ["irretrievably"], "-1.6 8.4 9.5": ["respectably"], "-5.1 16.8 8.4": ["mitzvah"], "3.9 9.9 -3.6": ["indicts"], "9.3 12.8 15.6": ["repopulate"], "2.9 0.3 4.2": ["prexy"], "8.9 2.9 31.8": ["carver"], "6.7 5.9 7.8": ["hurdled"], "7.8 8.4 5.7": ["favelas"], "6.4 12.3 7.0": ["capacitive"], "-2.2 3.3 -1.8": ["homilies"], "16.4 13.2 7.3": ["squinted"], "-3.0 13.5 2.2": ["influencer"], "7.3 3.4 0.9": ["adopter"], "12.9 7.0 0.8": ["farsighted"], "16.3 6.0 7.3": ["subindex"], "-4.7 14.4 13.3": ["naturalism"], "4.7 -2.0 5.4": ["encapsulating"], "12.9 5.1 2.0": ["metamorphosed"], "11.8 11.1 5.7": ["blackening"], "9.5 14.4 6.0": ["peculiarity"], "5.7 6.8 6.7": ["masterworks"], "3.1 10.0 7.5": ["wastefulness"], "2.0 20.8 3.3": ["antidotes"], "2.4 28.1 4.3": ["defeatism"], "10.3 32.0 9.7": ["reactionaries"], "5.4 7.3 12.6": ["eunuchs"], "-2.1 5.8 6.8": ["taluka"], "6.5 11.7 13.8": ["jaguars", "pard"], "2.7 -2.3 2.5": ["discontinuance"], "23.9 21.1 15.2": ["fiendish"], "2.0 11.7 8.3": ["beget", "implausibilities"], "3.7 5.3 8.7": ["ghrelin"], "-3.9 6.6 7.6": ["fasts"], "-4.3 7.8 4.4": ["oratorio"], "-1.9 10.9 7.2": ["temperaments"], "4.2 4.5 1.8": ["underpayment"], "6.9 13.0 0.6": ["sobriquet"], "14.7 5.2 5.4": ["signboard"], "8.7 -1.2 10.7": ["haute"], "8.2 15.1 11.7": ["lioness"], "4.8 15.4 29.1": ["cocks"], "6.1 5.7 6.9": ["converges"], "16.0 5.3 2.4": ["oases"], "-2.3 6.0 7.0": ["carcinoma"], "18.5 6.3 11.6": ["jiggle"], "0.7 2.5 12.1": ["soirees"], "4.6 2.9 5.5": ["rockstar"], "-3.7 1.7 6.3": ["eldercare"], "5.6 11.7 8.5": ["deadbeats"], "-1.1 -0.2 2.2": ["hepatic"], "22.0 15.1 23.1": ["tarantula"], "8.9 6.6 6.6": ["misting"], "6.5 2.9 6.8": ["dross"], "1.6 5.6 3.4": ["greenlit"], "10.2 7.7 17.0": ["squawk"], "16.5 8.2 6.6": ["peed"], "9.5 10.4 0.3": ["evacuates"], "2.6 5.5 0.1": ["embeddable"], "13.7 11.2 10.6": ["locomotion"], "4.1 9.4 20.6": ["utensil"], "22.8 14.4 19.2": ["pinata", "wacker"], "12.5 15.9 5.9": ["blackest"], "6.1 0.9 12.2": ["roadhouse"], "3.4 10.1 -5.6": ["repudiating"], "19.2 15.7 4.8": ["incinerating"], "6.4 8.0 24.2": ["sprig"], "5.8 -7.4 7.9": ["triennial"], "-2.7 14.0 12.6": ["cadences"], "-1.4 -1.2 2.8": ["laypeople"], "4.5 13.6 6.9": ["mater"], "-1.2 12.0 -1.2": ["lessors"], "4.4 1.0 6.7": ["eventuate"], "2.5 8.5 10.1": ["sidewall"], "-1.2 5.7 12.4": ["paintwork"], "-3.9 4.9 5.3": ["biosimilars", "mst"], "13.4 10.6 10.7": ["geez"], "8.3 9.7 14.9": ["fu"], "2.1 8.9 24.6": ["warblers"], "12.3 9.1 17.0": ["flaccid"], "0.1 2.7 0.7": ["fm"], "-0.2 3.3 5.9": ["investable"], "22.8 18.2 6.9": ["overlord"], "17.7 17.2 27.7": ["nymph"], "6.7 -3.7 -2.3": ["customizes"], "9.7 18.4 -0.1": ["repels"], "10.9 17.3 3.4": ["hisses"], "21.1 13.7 15.7": ["luminescent"], "8.1 3.8 15.0": ["sprees"], "-5.1 8.3 5.8": ["kinases"], "-3.4 13.2 9.3": ["middles"], "8.3 31.7 7.5": ["commandoes"], "0.0 3.6 2.9": ["binaries"], "18.6 9.3 9.5": ["entranceway"], "-1.2 1.7 1.6": ["cleansers"], "18.3 -3.4 6.3": ["nixing"], "22.7 15.5 17.7": ["frickin"], "6.8 9.2 14.6": ["imperiling"], "1.2 4.3 2.3": ["weblogs"], "-7.0 7.2 0.8": ["larcenies"], "11.1 11.9 9.1": ["ottoman"], "-0.1 3.6 9.4": ["harmonics"], "1.4 1.2 2.6": ["embezzle"], "-2.3 7.5 4.8": ["timelessness"], "-11.8 -5.3 7.0": ["antipsychotics"], "8.8 19.3 11.0": ["braves"], "14.2 13.7 2.9": ["doubtlessly"], "6.9 0.3 4.7": ["forthe"], "0.6 17.7 1.1": ["oversimplification"], "2.5 3.6 18.6": ["hydroponics"], "7.5 5.4 3.8": ["wined"], "9.1 -5.2 16.2": ["tiaras"], "0.9 8.6 8.2": ["newscasters"], "0.8 15.7 9.8": ["madder"], "3.9 10.5 2.3": ["ghosted"], "1.8 -8.8 7.0": ["bioplastics"], "2.5 14.3 27.2": ["peonies"], "-2.9 9.7 5.6": ["hopefulness"], "9.7 4.0 8.4": ["writhed"], "-0.4 11.8 1.7": ["transference"], "25.3 5.0 5.2": ["dinky"], "3.4 6.2 -4.4": ["lockerroom"], "10.1 17.1 -2.8": ["animates"], "12.0 17.0 12.8": ["castaway"], "4.1 30.0 5.9": ["leakers"], "10.4 6.4 6.2": ["vanities"], "-1.4 10.9 12.6": ["dither"], "-0.0 6.6 -1.4": ["invocations"], "0.2 10.8 9.8": ["decryption"], "11.3 4.4 20.2": ["rotisserie"], "12.1 10.7 11.1": ["twit"], "0.6 16.5 8.0": ["whiner"], "3.5 12.5 2.0": ["shackling"], "-1.2 2.5 12.0": ["foreskin"], "8.9 11.8 9.2": ["dirge"], "1.3 5.5 5.1": ["prenup"], "6.6 9.3 2.5": ["typist"], "17.4 12.0 1.8": ["starkest"], "2.5 0.3 6.1": ["geosciences"], "5.3 11.6 25.4": ["dhow"], "-2.8 -1.6 11.3": ["fractionation"], "1.0 4.1 6.5": ["underlain"], "9.4 6.3 6.0": ["shockers"], "3.5 10.6 2.3": ["nosebleed"], "4.5 20.7 10.9": ["hothead"], "4.4 12.5 -1.5": ["adminstration"], "6.6 9.3 26.9": ["kiwis"], "11.5 21.0 20.7": ["buggers"], "-1.4 5.7 6.6": ["virtualizing"], "8.1 20.2 14.0": ["rascals"], "11.7 9.6 8.5": ["someones"], "-2.9 4.9 -3.1": ["feedbacks"], "6.8 -0.1 -6.2": ["reclassifying"], "13.4 15.3 8.3": ["slanting"], "11.8 18.5 16.8": ["lance"], "17.7 9.1 0.1": ["detaching"], "10.4 8.1 9.3": ["stymies"], "3.3 3.7 21.8": ["fiddlers"], "11.3 3.3 -3.3": ["merchandisers"], "9.7 7.2 28.2": ["bluebird"], "8.9 9.4 14.6": ["minstrel"], "-4.4 7.2 6.9": ["clitoris"], "0.7 -0.2 9.7": ["shareware"], "12.9 10.5 4.1": ["commoditization"], "7.8 3.1 2.5": ["rs"], "-0.6 8.2 12.3": ["waterlogging"], "15.4 5.7 10.5": ["creak"], "6.2 4.4 11.0": ["compactor"], "-1.1 0.1 -1.9": ["thermoelectric"], "-8.0 3.7 3.2": ["manufacturability"], "5.8 1.9 8.9": ["laxative"], "21.1 -0.9 -2.1": ["ltd"], "-7.8 7.2 3.2": ["remitting"], "3.2 4.7 9.0": ["streetscapes"], "2.7 9.4 14.2": ["carotenoids"], "14.2 18.8 8.4": ["basher"], "-0.0 12.8 2.6": ["superconductivity"], "10.0 20.0 11.5": ["vitals"], "-7.9 4.4 7.6": ["payor"], "-1.5 -4.7 8.2": ["tenofovir"], "6.3 15.9 0.1": ["humanizing"], "4.6 2.5 4.0": ["shredders"], "-1.3 4.7 -4.1": ["dedications"], "4.3 11.4 4.6": ["industrially"], "15.7 19.9 9.1": ["obediently"], "2.9 -0.7 9.2": ["liveliness"], "11.6 4.5 3.3": ["maestros"], "-2.7 7.6 4.6": ["virologist"], "4.4 4.1 12.9": ["beeswax"], "7.0 7.4 12.0": ["garrulous"], "-5.2 0.8 0.8": ["freephone"], "6.7 6.7 2.4": ["gusted"], "6.8 10.2 5.4": ["spatially"], "4.5 12.9 -1.3": ["discretely"], "1.5 1.9 10.3": ["thermoplastic"], "-5.5 10.8 9.3": ["quilter"], "-0.8 7.2 4.0": ["scorekeeper"], "2.9 17.3 6.7": ["meddlesome"], "8.9 -1.4 9.8": ["trawled"], "12.7 9.9 10.0": ["whisks"], "2.9 10.7 8.2": ["clenching"], "12.3 26.3 1.3": ["massacring"], "4.0 7.3 6.5": ["caressed"], "-2.9 4.0 60.7": ["crabbers"], "11.4 4.8 4.0": ["enshrining"], "-1.5 -3.3 18.3": ["stallholders"], "6.8 12.7 1.2": ["oversimplified"], "-5.0 3.5 -4.1": ["angiography"], "6.3 8.0 16.1": ["rockfall"], "-16.2 1.5 1.0": ["benzodiazepines"], "-2.9 34.5 9.1": ["rifleman"], "2.6 6.6 14.0": ["shires"], "-1.0 2.2 2.1": ["expandability"], "3.1 12.7 11.8": ["kook"], "0.3 9.0 3.8": ["crosswinds"], "-0.2 14.7 5.9": ["compartmentalized"], "-8.0 5.3 3.7": ["audiophiles"], "20.0 7.1 7.3": ["ripoff"], "4.4 7.1 -0.5": ["palpitations"], "-1.4 13.4 8.9": ["ingratiating"], "21.4 1.7 4.6": ["superfast"], "7.4 8.3 3.5": ["dabbing"], "3.2 10.5 7.2": ["boyband"], "-5.2 4.8 1.4": ["subdistrict"], "4.7 8.6 39.9": ["cockles"], "2.6 8.6 12.2": ["xp"], "5.3 22.7 7.7": ["depredations"], "-1.8 16.9 9.9": ["thankfulness"], "-0.3 0.3 20.6": ["wetsuits"], "17.3 17.6 12.0": ["scythe"], "-2.4 15.2 16.0": ["mealtimes"], "-1.1 27.7 3.0": ["conscript"], "1.8 10.9 5.8": ["corruptly"], "4.9 18.6 32.9": ["shoal"], "13.3 11.7 13.7": ["joysticks"], "-1.5 15.3 4.0": ["seceded"], "8.8 4.5 14.1": ["swampland"], "-4.4 6.0 -0.1": ["angiogram"], "-1.2 8.3 9.2": ["prion", "amyloidosis"], "6.8 10.5 16.9": ["dandruff"], "9.6 13.7 11.1": ["eviscerate"], "21.6 8.7 3.7": ["afterall"], "-1.5 7.8 3.0": ["plusses"], "-0.4 30.1 0.3": ["resisters"], "5.0 5.5 6.9": ["vocabularies"], "13.8 2.4 25.7": ["birdhouse"], "-7.7 5.1 7.3": ["unraced"], "0.6 7.8 6.0": ["insertions"], "0.5 6.9 -0.1": ["recalibrated"], "7.8 11.8 19.5": ["cleaver"], "2.3 6.9 -2.1": ["dilation"], "6.3 7.8 15.6": ["emoticons"], "-1.4 7.3 5.9": ["tunable"], "-3.4 3.9 3.2": ["grantee"], "4.2 7.3 3.2": ["mein"], "5.1 8.5 16.0": ["antispyware"], "0.2 13.2 2.4": ["siled"], "-7.0 7.3 2.5": ["deferments"], "5.0 15.4 9.3": ["egalitarianism"], "3.9 8.5 5.6": ["dusts"], "12.3 6.7 1.9": ["stubbed"], "5.2 -1.2 4.7": ["cheapened"], "5.3 12.0 10.7": ["misreporting"], "6.5 10.0 10.1": ["blushed"], "1.9 12.8 3.0": ["rephrase"], "7.8 11.4 9.2": ["paternalism"], "-8.4 5.3 7.5": ["parkways"], "5.0 0.6 -4.9": ["deodorants"], "0.0 1.9 -5.4": ["arbitrations"], "-3.3 1.1 4.0": ["radiographic"], "5.9 6.5 1.7": ["ambassadorship"], "10.0 0.5 5.1": ["barbershops"], "9.5 8.7 21.0": ["virility"], "7.4 5.8 4.9": ["armrests"], "-6.4 3.4 5.4": ["decisioning"], "5.0 -7.5 -2.5": ["facelifts"], "-0.4 10.3 -3.0": ["harangue"], "3.1 5.6 -0.8": ["abolishes"], "4.3 7.2 9.0": ["warbling"], "7.7 0.4 3.8": ["predating"], "-6.1 6.2 -0.2": ["beleive"], "1.3 4.8 -4.9": ["felicitate"], "1.2 4.6 4.9": ["amortize"], "-2.6 7.8 3.0": ["excitation"], "3.8 19.1 8.5": ["internecine"], "12.1 16.8 30.2": ["scaly"], "3.7 2.0 12.9": ["cabdriver"], "7.5 26.3 3.1": ["gamed"], "-6.7 5.4 2.1": ["convertibility"], "5.5 9.6 4.4": ["weve"], "12.2 1.5 3.3": ["tooled"], "12.7 7.9 9.3": ["gigawatt"], "1.8 8.9 4.6": ["amuses"], "13.7 24.0 6.0": ["scumbags"], "5.5 10.5 12.0": ["apologetically"], "2.4 9.6 9.7": ["nonfatal"], "2.2 16.6 8.1": ["consecrate"], "10.8 22.8 5.2": ["bugaboo"], "3.0 4.5 -0.8": ["recused"], "6.9 -3.1 4.8": ["switchgear"], "-0.7 15.0 8.9": ["phytochemicals"], "17.1 5.6 18.7": ["cubed"], "18.3 11.2 18.5": ["silken"], "-8.9 7.3 -1.9": ["audiologist"], "4.3 13.6 9.5": ["metaphysics"], "-2.2 5.5 5.8": ["reconstituting"], "5.8 23.1 5.7": ["eachother"], "-2.3 8.9 3.5": ["westernized"], "13.0 11.7 1.6": ["bedfellows"], "-2.9 5.7 2.4": ["emoluments"], "-7.0 0.9 3.4": ["debugger"], "11.3 7.5 11.4": ["bimbo"], "2.0 6.7 25.5": ["fajitas"], "1.3 2.3 4.4": ["octaves"], "-4.5 7.7 6.3": ["filmography"], "4.9 2.5 18.9": ["crunk"], "-4.3 -0.0 0.9": ["commutations"], "-4.3 3.8 1.9": ["programmability"], "-10.3 -0.4 -1.0": ["locum"], "0.7 1.1 15.6": ["soyabean"], "-6.0 13.5 -4.6": ["condemnable"], "3.3 -5.7 2.7": ["bedsheet"], "-3.1 -8.1 7.1": ["creatine"], "-4.1 1.6 7.8": ["compere"], "6.9 12.1 3.9": ["derring"], "0.1 17.1 12.0": ["modifier"], "5.4 13.0 4.1": ["vicarious"], "-0.9 5.8 10.5": ["mucked"], "-2.2 5.7 0.5": ["typewritten"], "5.5 22.3 4.7": ["jingoistic"], "15.8 7.8 16.1": ["cowbells"], "2.0 5.8 13.1": ["miller"], "9.1 6.4 17.4": ["eddy"], "7.4 0.8 6.7": ["ethicist"], "-1.6 15.5 12.3": ["pollinated"], "14.0 3.1 5.7": ["spurns"], "5.7 14.7 7.1": ["fixate"], "5.4 2.6 1.1": ["bounceback"], "8.0 10.4 5.6": ["exoplanets"], "9.8 10.4 4.1": ["waster"], "-1.9 9.3 23.7": ["yolks"], "4.6 8.7 8.6": ["whinge"], "8.6 10.8 10.4": ["tranquilizer"], "6.1 11.1 13.1": ["git"], "-5.3 0.6 5.7": ["spasticity"], "4.7 21.0 2.7": ["azimuth"], "14.2 -1.6 10.8": ["dollops"], "2.1 6.6 3.2": ["idleness"], "-6.8 6.1 -1.0": ["involvements"], "12.3 10.3 8.0": ["buffoons"], "21.4 6.0 6.3": ["nestle"], "0.1 10.9 22.4": ["motorboats"], "-0.8 0.5 0.0": ["systolic"], "13.5 5.0 14.2": ["strainer", "calaveras"], "17.6 7.8 8.5": ["contentedly"], "-5.2 1.5 2.0": ["biosafety"], "2.0 5.8 -6.5": ["masturbated"], "0.6 0.1 10.5": ["trendier"], "2.1 10.3 10.7": ["coaxial"], "-2.5 7.6 17.4": ["liqueurs"], "5.2 10.9 0.0": ["outspending"], "0.5 1.0 -1.9": ["audiology"], "6.2 -1.9 15.9": ["meatier"], "7.9 -1.1 4.7": ["debarred"], "-9.2 3.5 2.2": ["aliyah"], "-2.3 3.7 4.2": ["angioplasties"], "9.3 -0.1 4.8": ["pacifiers"], "2.0 7.5 13.0": ["censuses"], "2.1 11.1 9.7": ["grubber"], "-2.4 7.8 2.2": ["ghostwriter"], "0.3 11.8 2.8": ["disuse"], "-0.9 -6.8 8.8": ["ct"], "13.2 3.8 5.9": ["rejig"], "7.6 3.9 5.6": ["virtualised"], "5.1 11.8 16.0": ["defund"], "-3.0 1.2 -3.4": ["outdistanced"], "9.8 3.0 0.3": ["rekindles"], "2.2 3.5 0.6": ["belive"], "13.9 4.0 18.0": ["chihuahua"], "0.7 5.0 -2.1": ["redressal"], "-1.0 14.0 6.0": ["cisterns"], "9.9 8.9 6.4": ["british"], "-4.9 4.2 11.0": ["outvoted"], "-3.0 6.4 12.7": ["derogation"], "5.0 12.8 13.6": ["contrivance"], "13.9 10.0 8.8": ["swivels"], "22.1 7.6 18.2": ["glimmering"], "4.2 15.0 6.5": ["sicknesses"], "4.1 7.5 21.1": ["trowel"], "9.7 14.5 10.2": ["starlight"], "5.5 16.4 7.3": ["pisses"], "9.0 8.9 0.5": ["peephole"], "6.4 13.4 9.7": ["immobility"], "4.2 13.5 10.4": ["effete"], "-1.1 7.7 -4.6": ["nonsectarian"], "-4.9 13.8 5.3": ["inferring"], "23.5 4.7 -1.9": ["stampeding"], "11.7 -2.1 7.6": ["scrapyard"], "12.7 13.0 10.4": ["miming"], "-6.2 -5.7 10.7": ["callbacks"], "7.5 11.6 3.7": ["flashbulbs"], "15.1 8.5 2.6": ["hijacks"], "8.5 6.9 1.2": ["nk"], "13.1 -2.1 9.1": ["foots"], "3.5 -6.3 7.2": ["telenovelas"], "1.1 12.6 17.9": ["decaf"], "6.8 8.2 4.0": ["localizing"], "11.6 11.0 13.3": ["blandness"], "2.0 6.2 4.7": ["crystallization"], "-0.9 17.0 11.4": ["fourball"], "3.4 3.0 8.7": ["groomers"], "10.3 5.8 14.3": ["containerized"], "-9.4 18.8 -2.3": ["antisemitism"], "2.1 -3.9 2.0": ["fulsome"], "11.9 14.7 12.1": ["douche"], "0.5 1.5 9.2": ["indium"], "12.4 9.9 7.9": ["giddily"], "4.1 3.8 5.0": ["sews"], "15.8 10.0 15.9": ["tabletops"], "10.9 2.7 2.7": ["dermatitis"], "22.1 13.4 6.3": ["monoculture"], "7.8 2.6 8.3": ["masseur"], "2.6 5.7 10.7": ["webcasters"], "5.8 5.1 8.6": ["medicate"], "4.2 8.9 16.2": ["vertebrate"], "2.5 7.8 4.9": ["tradeable"], "3.9 8.7 1.6": ["hassling"], "3.5 5.7 7.5": ["abscesses"], "11.6 6.2 8.4": ["plod", "effets"], "-1.7 14.1 9.8": ["biofilm"], "-6.0 16.5 7.1": ["favorability"], "-6.6 2.5 -0.1": ["concurring"], "17.9 9.0 10.7": ["semicircle"], "2.9 -0.5 2.2": ["triplet"], "-2.4 6.0 12.6": ["coronavirus"], "-4.4 1.9 2.4": ["prolongation"], "6.7 12.5 4.6": ["stuntmen"], "1.2 17.2 1.3": ["ceasefires"], "2.6 13.2 7.3": ["reverently"], "8.2 19.4 13.7": ["pickpocket"], "1.2 0.2 6.8": ["titillation"], "12.9 3.3 14.3": ["punctuates"], "-3.4 7.1 8.8": ["chromosomal"], "1.2 16.2 2.4": ["sycophantic"], "1.8 17.4 -2.5": ["diffusing"], "-3.3 4.9 5.7": ["entourages"], "-1.0 13.7 -3.3": ["retakes"], "11.7 9.6 15.0": ["famished"], "0.9 6.5 8.0": ["liveable"], "-3.3 3.1 -1.1": ["educationist"], "-2.4 6.6 25.2": ["rhododendrons"], "-1.6 23.5 5.2": ["grievously"], "4.0 6.8 3.6": ["mickey"], "-1.3 9.0 -0.2": ["bookmarked"], "9.7 13.2 8.9": ["hick"], "-4.8 14.8 23.9": ["homeport"], "-1.9 13.0 2.9": ["undervaluation"], "11.2 4.8 12.0": ["chris"], "17.3 12.0 12.5": ["squirts"], "8.9 21.2 6.8": ["libs"], "0.3 6.5 4.6": ["modal"], "14.8 15.5 8.4": ["hangman"], "3.4 4.3 9.0": ["stochastic"], "12.6 14.7 0.9": ["enlarges"], "24.5 21.0 31.8": ["piranha"], "13.5 10.6 9.4": ["longingly"], "22.6 0.8 0.5": ["demerged"], "-3.5 15.2 -1.4": ["inactions"], "11.3 15.2 10.2": ["scatters"], "14.8 -0.1 2.5": ["scotched"], "11.4 9.9 9.0": ["grasscourt"], "8.2 -0.2 4.8": ["stickier"], "6.8 2.1 13.9": ["flaking"], "2.3 8.5 4.9": ["gage"], "10.9 4.0 8.7": ["henhouse"], "4.2 1.3 -3.1": ["restyled"], "12.6 4.2 15.0": ["jones"], "3.6 8.9 4.4": ["sexualized"], "-3.2 11.8 2.5": ["dacoity"], "3.7 16.8 3.9": ["maneuverable"], "7.5 29.7 13.2": ["gunboats"], "1.3 3.9 6.8": ["townwide"], "-2.0 5.9 7.5": ["thoracic"], "3.0 19.5 5.2": ["detests"], "14.2 1.3 3.8": ["photocopier"], "6.8 2.8 3.1": ["overvaluation"], "3.3 18.7 4.7": ["unipolar"], "6.1 0.3 8.5": ["decriminalize"], "8.9 8.7 15.1": ["domesticity"], "-7.2 9.3 5.5": ["surmises"], "4.9 4.0 4.4": ["juked"], "3.5 6.1 27.7": ["mainlanders"], "-1.6 2.1 -2.1": ["advisability"], "4.8 21.9 16.3": ["rascal"], "-2.5 0.2 16.0": ["watersports"], "-2.8 -1.6 1.4": ["recheck"], "5.0 10.6 8.9": ["tailenders"], "11.8 9.4 9.5": ["twirls"], "6.3 23.7 7.2": ["omniscient"], "4.1 5.7 21.5": ["catamarans"], "1.3 24.0 14.4": ["peasantry"], "-4.2 3.6 -3.1": ["fistula"], "-3.5 9.0 4.7": ["confiding"], "7.5 17.8 7.7": ["photogs"], "4.2 5.8 0.8": ["kmh"], "-1.8 14.6 -1.1": ["checkpost"], "-0.1 6.0 1.2": ["motorhomes"], "2.6 1.8 12.7": ["milliliter"], "0.4 10.3 -0.6": ["reorientation"], "-6.9 8.1 59.4": ["groundfish"], "7.3 3.6 2.3": ["trialed"], "-5.4 3.3 17.5": ["dairying"], "-0.2 -1.9 -2.2": ["bureaux"], "-0.4 6.0 8.6": ["breccia"], "-1.2 4.5 6.8": ["refrigerants"], "14.4 3.3 8.1": ["thermo"], "-3.3 7.2 8.0": ["phosphorylation"], "12.8 14.1 4.7": ["savaging"], "4.1 -2.4 -0.1": ["bookrunners"], "-4.1 12.6 4.9": ["likeminded"], "-6.5 5.9 3.7": ["serviceability"], "1.5 -2.1 9.7": ["multiplexing"], "16.4 18.0 27.7": ["bumblebees"], "14.1 6.7 7.9": ["slouching"], "13.9 9.9 6.3": ["goody"], "13.4 9.7 12.7": ["tykes"], "2.7 8.5 2.5": ["looker"], "-3.5 8.0 -1.3": ["saddens"], "5.4 6.9 23.5": ["sprigs"], "19.3 8.3 9.1": ["dioramas"], "3.4 11.5 2.4": ["hectoring"], "2.2 7.8 8.1": ["ian"], "0.3 3.4 14.4": ["lamination"], "9.7 11.6 -2.1": ["outclass"], "-4.8 11.4 -1.2": ["refutation"], "4.8 4.4 2.3": ["statesmanlike"], "5.7 27.9 4.5": ["heros"], "-6.0 8.5 4.8": ["moisturizers"], "-5.5 2.9 8.7": ["washouts"], "6.1 2.8 11.8": ["adornments"], "9.6 7.5 14.8": ["relents"], "16.5 -1.4 10.0": ["sweetens"], "2.6 6.9 10.3": ["databook"], "5.8 19.0 5.2": ["sociopathic"], "12.2 11.4 0.1": ["conmen"], "-7.3 5.5 4.3": ["spudded"], "11.3 20.3 6.9": ["pinging"], "3.6 3.7 30.2": ["lettuces"], "9.5 7.0 6.2": ["tomfoolery"], "7.6 8.8 7.2": ["redeems"], "5.5 8.4 9.9": ["reflectivity"], "2.8 16.2 11.6": ["longball"], "14.8 10.9 4.8": ["mommies"], "-1.4 10.0 12.4": ["avocation"], "-5.0 11.9 7.1": ["anatomic"], "4.7 9.4 8.1": ["catatonic"], "4.1 3.8 1.7": ["guestbook"], "4.4 15.4 14.1": ["bros"], "21.0 17.7 25.1": ["piranhas"], "15.2 4.8 10.3": ["pompoms"], "-4.1 13.9 6.1": ["decolonization"], "6.9 1.0 6.4": ["kroons"], "21.2 30.7 8.8": ["infernal"], "9.0 21.8 3.4": ["cunningly"], "-7.5 1.6 3.7": ["compressions"], "-7.7 -4.7 10.6": ["submittal"], "13.4 5.2 7.2": ["bisects"], "2.9 11.6 16.5": ["artefact"], "-5.3 14.8 1.8": ["weaponization"], "5.1 11.3 27.6": ["daffodil"], "5.3 4.9 10.0": ["groundskeepers"], "19.6 9.9 6.0": ["ultramodern"], "-5.5 6.3 17.4": ["dinghies"], "2.5 14.8 7.9": ["shallowness"], "2.9 15.3 4.9": ["unpatched"], "4.3 18.1 11.4": ["aphorism"], "-0.7 3.7 10.5": ["outwith"], "-9.0 -1.8 -1.0": ["activewear"], "5.3 -0.2 14.7": ["yurt"], "-1.0 5.5 13.1": ["herbalist"], "17.5 9.4 15.5": ["crud"], "-1.3 7.3 11.0": ["alluvial"], "0.1 4.8 21.9": ["flaxseed"], "-3.9 8.3 10.1": ["kimberlites"], "2.0 9.4 22.9": ["shipowners"], "8.2 8.4 -1.4": ["headrest"], "-5.4 2.7 6.1": ["inaugurations"], "15.1 4.4 6.4": ["redheaded"], "-5.8 2.3 5.8": ["replicable"], "0.9 14.6 12.4": ["womenfolk"], "30.8 16.7 18.1": ["anthropomorphic"], "24.6 12.1 4.0": ["shills"], "9.2 10.7 6.6": ["dejection"], "-4.3 15.8 11.2": ["trier"], "3.4 3.8 16.1": ["hybridization"], "3.7 17.3 12.9": ["windward"], "1.8 10.4 13.4": ["lye"], "3.3 -0.3 9.4": ["floriculture"], "5.7 6.7 13.5": ["lithograph"], "12.4 4.7 19.8": ["grayish"], "12.5 10.3 9.2": ["overlaying"], "7.1 2.1 2.4": ["outjumped"], "0.9 12.3 14.8": ["homeboy"], "12.2 3.8 20.8": ["squashes"], "3.6 9.0 12.7": ["minutia"], "-1.1 -7.0 -0.3": ["accomodation"], "1.3 10.9 12.5": ["ragweed"], "0.3 7.7 6.3": ["jaundiced"], "5.2 1.4 16.3": ["polythene"], "4.3 3.1 31.7": ["lentil"], "7.3 30.2 5.1": ["militiaman"], "11.1 1.3 14.4": ["smidge"], "9.3 10.3 15.3": ["dumbbell"], "15.5 14.8 8.9": ["ancients"], "3.5 5.2 24.9": ["fronds"], "8.2 -4.6 5.1": ["las"], "-2.0 13.3 5.0": ["admonishes"], "-12.2 2.3 -3.0": ["ocb"], "2.3 16.1 13.8": ["monarchies"], "-8.2 5.8 -5.6": ["secondarily"], "6.1 11.9 11.4": ["duff"], "2.8 14.6 2.7": ["parkour"], "16.1 -0.2 6.3": ["gyrated"], "-1.7 5.0 12.7": ["ripeness"], "-11.5 4.2 1.8": ["elucidated"], "-2.3 6.6 -0.6": ["hydrating"], "4.9 5.1 14.6": ["sublimely"], "0.5 9.7 -0.2": ["receptivity"], "-4.0 -1.3 2.0": ["comprehensiveness"], "0.8 -8.5 4.8": ["sabbaticals"], "-0.7 -4.3 1.3": ["panellist"], "-1.6 3.7 11.2": ["paybacks"], "2.7 2.0 12.3": ["stackable"], "-3.2 12.7 8.5": ["infirmity"], "0.1 7.8 9.7": ["intermingling", "neuromusculoskeletal"], "7.6 1.0 13.7": ["folkloric"], "4.4 8.6 -5.3": ["soundproof"], "8.8 11.4 11.8": ["wallflower"], "4.1 14.7 4.2": ["coddle"], "-7.0 7.5 3.0": ["misconducts"], "1.6 8.8 2.6": ["engendering"], "17.5 0.5 12.7": ["xylophone"], "-5.0 8.0 3.6": ["scorebook"], "-2.0 11.2 18.4": ["heartworm"], "4.4 -4.8 -3.5": ["reformatted"], "-7.6 9.2 2.5": ["movingly"], "11.3 -3.0 14.2": ["nouveau"], "-3.6 16.2 5.9": ["worldviews"], "8.6 12.2 10.2": ["indignantly"], "0.8 1.7 17.3": ["flapper"], "-9.7 6.8 9.8": ["longshots"], "-5.1 14.3 3.2": ["ostracism"], "3.4 10.7 12.4": ["extractive"], "-2.2 7.3 -2.6": ["stenographer"], "-2.9 6.9 7.4": ["minicar"], "-0.8 -3.2 5.7": ["conservatories"], "-1.8 19.9 -0.3": ["falsity"], "6.2 5.0 18.2": ["mustang"], "-7.5 -2.4 1.8": ["configurability"], "10.1 2.5 4.8": ["shooed"], "-1.9 29.9 -1.3": ["incapacitating"], "4.3 8.1 9.1": ["coos"], "6.4 5.7 11.0": ["laneway"], "13.4 13.6 11.5": ["cityscapes"], "6.8 10.1 2.0": ["circumvents"], "-3.3 7.4 14.0": ["follicles"], "2.6 6.2 -0.8": ["slagging"], "7.6 15.9 9.1": ["clumsiness"], "11.0 -2.3 13.5": ["buskers"], "22.7 25.7 2.6": ["blaster"], "-2.8 8.8 2.1": ["imbues"], "-1.4 9.7 11.2": ["drainages"], "-4.7 1.3 5.9": ["urinalysis"], "8.4 9.0 15.5": ["metalwork"], "-2.7 -1.2 14.8": ["khat"], "2.7 -0.4 5.3": ["bidirectional"], "9.0 24.2 4.9": ["incarnate"], "1.7 16.1 4.5": ["homestanding"], "-0.0 2.6 6.9": ["sills"], "1.1 8.2 6.0": ["untill"], "3.2 7.1 9.0": ["boudoir", "uncast"], "-0.0 1.4 11.5": ["maglev"], "4.2 6.5 3.9": ["savvier"], "6.0 9.2 5.1": ["muting"], "0.8 3.4 6.1": ["whipsawed"], "-4.3 15.8 20.7": ["birder"], "-2.1 5.4 7.8": ["woodwinds"], "11.7 17.9 0.6": ["scourges"], "6.6 13.5 0.6": ["propagates"], "6.7 11.6 4.8": ["entryways"], "18.6 5.3 6.8": ["discoverer"], "8.1 9.8 3.0": ["entrancing", "qv"], "18.3 13.1 21.0": ["slurp"], "0.1 13.1 4.4": ["instate"], "22.9 7.7 10.9": ["swoosh"], "5.4 8.1 3.8": ["sterner"], "-0.4 9.2 13.3": ["fistfights"], "2.9 6.3 14.3": ["welling"], "2.2 8.4 16.2": ["throwbacks"], "5.7 18.5 8.8": ["cackle"], "1.3 5.0 8.4": ["condenser"], "5.4 -8.6 -0.9": ["cofounded"], "-5.2 9.7 -1.5": ["warrantless"], "6.2 17.0 8.5": ["popups"], "2.4 14.3 4.1": ["mutilate"], "11.5 2.8 11.5": ["australia"], "12.7 10.0 -0.3": ["coziness"], "4.4 15.3 1.4": ["dupes"], "12.8 16.4 9.9": ["molester"], "15.2 8.2 5.7": ["ceremonially"], "4.4 -6.2 -1.5": ["harkened"], "4.4 3.6 2.3": ["watermarks"], "-10.4 5.0 3.7": ["insurable"], "-1.6 -0.2 13.9": ["pastes"], "17.2 3.6 9.0": ["untangling"], "6.2 8.5 11.4": ["pharaohs"], "1.7 8.6 6.7": ["decays"], "17.1 12.7 15.9": ["shapeless"], "5.2 7.5 10.6": ["whingeing"], "-2.4 16.2 10.7": ["stratigraphic"], "-0.1 2.5 4.8": ["uncredited"], "1.2 9.6 17.3": ["grapevines"], "8.6 12.6 8.2": ["tramping"], "-8.7 -0.3 10.0": ["naltrexone"], "-0.1 21.3 -0.6": ["jawan"], "12.6 2.1 24.0": ["chomped"], "-3.6 7.0 12.3": ["cohabiting"], "21.0 6.9 5.2": ["latecomer"], "2.4 0.4 -5.9": ["commendably"], "-0.6 3.4 4.9": ["pervious"], "5.3 2.8 9.2": ["hematite"], "5.5 4.3 8.9": ["satiated"], "-1.2 4.0 6.5": ["recency"], "-3.2 13.5 1.7": ["uncorroborated"], "2.3 8.4 11.4": ["merch"], "9.2 2.8 7.4": ["wat"], "-5.4 13.1 -5.9": ["promulgating"], "9.3 13.6 17.6": ["elms"], "-3.9 21.7 -0.5": ["safehouse"], "4.6 6.4 6.5": ["payphone"], "7.1 15.4 13.7": ["balaclava"], "5.6 2.6 6.6": ["twangy"], "17.8 27.7 9.8": ["boogeyman"], "11.1 22.3 1.8": ["paymasters"], "11.4 12.8 16.3": ["wart"], "19.1 0.7 8.9": ["trundled"], "-1.1 4.7 8.8": ["darshan"], "-13.7 9.0 7.9": ["hospitalists"], "11.9 3.2 14.2": ["laurel"], "3.3 8.6 5.2": ["lib"], "6.7 1.3 -5.7": ["interfaced"], "11.1 15.8 12.3": ["antipiracy"], "-4.5 12.6 -0.4": ["radiosurgery"], "-5.3 -0.7 14.5": ["reconvening"], "-0.4 14.4 10.6": ["netroots"], "9.5 16.2 5.0": ["humanitarianism"], "1.8 3.2 -1.0": ["badged"], "1.7 -0.6 13.6": ["tpy"], "3.6 14.5 2.9": ["anchorwoman"], "4.7 21.3 6.8": ["houseguest"], "11.0 5.1 20.0": ["beech"], "-4.1 7.9 10.6": ["corneal"], "11.9 6.8 12.1": ["puking"], "6.3 5.5 11.4": ["pizzerias"], "-2.5 9.3 2.2": ["remediated"], "-0.2 10.7 4.1": ["confusions"], "2.5 9.2 5.9": ["airlifts"], "1.7 7.5 -1.5": ["tangibly"], "5.9 0.8 0.7": ["ans"], "3.5 6.0 8.4": ["calmest"], "-2.9 6.4 12.4": ["blk"], "14.2 0.7 -0.7": ["trialing"], "15.3 10.1 -0.2": ["masquerades"], "8.5 -1.5 12.4": ["layed"], "1.7 11.1 4.6": ["meddled"], "-10.2 11.2 6.1": ["soloing"], "4.3 21.0 3.1": ["cruelties", "lawed"], "11.7 11.3 6.3": ["densest"], "1.7 19.2 35.1": ["milfoil"], "6.6 8.7 23.8": ["redheads"], "20.3 18.6 -1.9": ["commandeering"], "17.3 7.7 4.8": ["subsector"], "9.5 6.6 -0.1": ["guzzle"], "2.9 6.5 5.4": ["restorer"], "4.8 6.7 5.1": ["dyno"], "-12.9 -2.5 12.5": ["expungement"], "4.8 -4.2 6.1": ["shoehorned"], "4.4 5.6 15.2": ["raisers"], "12.2 19.7 3.7": ["fusillade"], "5.7 14.8 8.9": ["satisfyingly"], "6.9 10.3 9.3": ["grazes"], "2.0 6.5 28.9": ["pho"], "0.9 9.7 11.9": ["dines"], "-3.7 15.6 -2.0": ["reconciliatory"], "-8.2 5.9 27.5": ["broilers"], "1.3 11.4 14.7": ["clays"], "6.7 16.6 18.6": ["royalists"], "-0.6 10.8 2.7": ["conciliator"], "6.4 14.4 7.9": ["catacombs"], "2.3 9.9 12.4": ["loosehead"], "17.7 14.5 12.5": ["cheerily"], "36.6 8.6 17.3": ["ginormous"], "-4.0 0.7 2.7": ["hypnotherapy"], "2.8 -1.6 6.8": ["styrene"], "9.3 8.4 12.9": ["chaebol"], "16.8 12.7 9.3": ["mangling"], "6.0 13.2 4.4": ["governess", "motorbiker"], "4.0 7.3 8.7": ["obeisance"], "-3.4 2.5 8.9": ["curtailments"], "0.8 7.6 26.5": ["garnishes"], "6.9 6.9 6.2": ["alphabetical"], "18.6 7.2 -7.7": ["electricals"], "7.9 -0.5 7.3": ["qoq"], "5.4 12.1 8.0": ["purrs"], "-2.1 1.2 5.5": ["rowdiness"], "8.1 -7.0 6.5": ["monogrammed"], "25.9 15.2 3.4": ["gremlins"], "10.6 5.4 11.9": ["tumbler"], "6.4 8.2 4.9": ["quenched"], "14.2 7.9 11.5": ["lopping"], "6.1 12.2 9.2": ["blandly"], "14.7 8.9 8.2": ["lumberyard"], "-0.4 8.8 4.0": ["brashness"], "8.2 7.2 3.3": ["bartered"], "2.6 10.6 8.6": ["mumbles"], "8.6 2.6 6.3": ["imprinting"], "-5.6 7.2 9.0": ["decisionmaking"], "-0.2 1.5 8.6": ["homemaking"], "-0.8 21.0 5.1": ["dangerman"], "-4.2 9.7 2.1": ["norepinephrine"], "-1.2 6.6 1.3": ["humidifier"], "-4.0 2.3 9.6": ["exco"], "-9.3 -0.4 6.6": ["munis"], "8.4 3.5 4.7": ["af"], "2.7 9.8 1.4": ["pilferage"], "1.3 2.9 7.9": ["carpools"], "5.3 16.1 7.5": ["synapse"], "-6.1 3.6 10.2": ["scrappage"], "12.0 0.1 12.2": ["spanish"], "2.5 10.2 21.1": ["tastebuds"], "10.2 13.5 4.1": ["westwards"], "4.8 12.0 2.3": ["mows"], "1.5 6.7 -0.7": ["expounding"], "6.5 9.1 6.7": ["butted"], "-4.1 13.4 18.9": ["birdwatchers"], "14.5 0.8 8.7": ["blighting"], "2.9 -1.1 30.1": ["plantains"], "7.9 20.5 16.8": ["hedgerows"], "-6.4 22.6 7.2": ["demilitarized"], "-8.6 9.9 10.8": ["recurs"], "-3.4 6.3 0.7": ["presidium"], "-3.5 -0.9 -10.5": ["substantiates"], "13.1 -1.7 4.7": ["shakier"], "-3.3 10.1 6.2": ["likeability"], "13.7 9.3 9.8": ["nosing"], "4.5 4.4 4.0": ["apparels"], "-3.3 4.1 10.6": ["adjuvants"], "-2.8 7.1 -5.2": ["vitally"], "-1.0 19.8 12.7": ["snitching"], "0.9 15.3 3.1": ["disfavor"], "8.6 6.6 2.8": ["cuddles"], "9.0 10.6 10.6": ["hacksaw"], "7.7 12.4 8.6": ["superficiality"], "-9.8 6.5 16.1": ["dryland"], "13.8 -4.6 -1.9": ["billowed"], "7.2 5.2 13.8": ["chocolatier"], "2.0 18.7 5.3": ["disarms"], "5.6 11.0 4.5": ["innuendos"], "-0.6 15.3 9.6": ["rootkits"], "-8.4 6.5 6.9": ["applicators"], "17.5 4.2 9.7": ["plopping"], "-5.6 21.2 -0.1": ["unpopulated"], "1.1 14.3 6.9": ["parenthesis"], "13.6 -2.8 16.5": ["rhinestone"], "6.9 6.8 5.1": ["needled"], "21.8 10.8 25.1": ["chipmunk"], "7.3 14.4 4.9": ["blacken"], "5.5 10.4 6.6": ["tinyurl"], "12.9 32.0 6.2": ["sentries"], "4.3 1.4 5.3": ["lifecycles"], "-4.7 6.2 9.5": ["erythropoietin"], "-5.2 0.2 2.1": ["timeshares"], "-14.7 3.6 3.2": ["antipsychotic"], "-5.4 1.1 19.8": ["meatless"], "10.5 -2.2 3.7": ["washboard"], "-5.8 13.0 -0.5": ["deactivation"], "10.1 5.4 10.6": ["sunbathers"], "14.3 10.7 -0.7": ["triumphal"], "3.3 4.6 8.2": ["offramp"], "17.0 10.1 10.9": ["sunning"], "11.3 -10.8 1.2": ["kickstarted"], "2.8 3.2 9.5": ["chalcopyrite"], "6.0 -6.4 18.0": ["rosewood"], "11.1 15.7 14.5": ["loonies"], "-0.5 7.5 32.4": ["tamarind"], "0.8 15.3 16.8": ["midshipman"], "0.6 3.5 8.1": ["helms"], "0.4 2.8 22.1": ["schoolies"], "-2.9 -1.2 4.6": ["tcf"], "5.5 7.3 29.4": ["deckhand"], "-4.0 21.6 9.2": ["unelectable"], "20.1 12.3 1.9": ["hardman"], "-2.5 6.3 -4.0": ["nonspecific"], "-2.6 23.1 12.1": ["secessionists"], "-8.1 0.5 8.7": ["genealogist"], "5.8 18.4 9.9": ["admiringly"], "0.7 11.4 1.7": ["resistivity"], "1.5 -0.5 -0.3": ["centralizes"], "10.3 0.5 9.7": ["beefier"], "10.9 4.8 8.1": ["capitols"], "7.5 5.9 12.8": ["bobbling"], "0.2 4.7 8.5": ["teleworking"], "-6.4 -0.6 7.8": ["rhodium"], "14.7 18.2 5.8": ["vaporize"], "6.1 8.6 6.9": ["postmen"], "10.7 -3.4 13.3": ["pokey"], "11.4 13.2 13.1": ["earthbound"], "0.5 4.9 11.5": ["overclocked"], "2.2 6.7 2.4": ["oration"], "3.9 5.5 2.5": ["headbutted"], "-2.2 5.4 14.1": ["calcification"], "5.1 3.1 10.7": ["rickets"], "9.0 9.4 19.3": ["dingo"], "-1.7 4.0 10.6": ["conjunctivitis"], "2.5 11.8 5.1": ["luminance"], "6.0 11.4 4.4": ["failsafe"], "4.8 4.7 10.7": ["odder"], "-5.6 20.5 9.1": ["enlistees"], "12.0 4.0 20.4": ["hubcaps"], "11.6 3.5 22.7": ["wallaby"], "-5.0 11.2 5.1": ["cytotoxic"], "-7.1 4.7 -6.0": ["correspondences"], "13.0 12.9 8.6": ["encroaches"], "10.5 9.7 2.5": ["lawbreaking"], "-2.0 7.3 11.0": ["heartsick"], "-1.4 6.2 20.3": ["drizzling"], "11.0 10.7 9.3": ["tripods"], "1.2 13.5 7.2": ["descriptor"], "0.9 5.6 7.1": ["sciatica"], "-0.0 8.5 10.3": ["flowerbeds"], "8.0 4.1 4.2": ["windscreens"], "3.9 8.6 3.4": ["misreported"], "12.2 1.2 -1.7": ["capacious"], "7.7 -4.5 2.6": ["petering"], "-4.4 4.5 11.5": ["raceday"], "-0.5 12.7 10.0": ["reenactments"], "-0.6 3.4 7.2": ["diazepam"], "18.1 -3.5 -3.3": ["milion"], "-7.9 5.5 0.2": ["demotions"], "16.0 4.0 15.0": ["plexiglass"], "-1.8 3.0 1.8": ["indentures"], "10.5 7.4 16.1": ["yucky"], "13.7 5.8 7.3": ["airbrushing"], "8.8 19.4 10.9": ["ourself"], "3.6 6.5 9.5": ["lecherous"], "2.0 8.5 9.2": ["monkeypox"], "-4.4 -1.9 10.3": ["trunking"], "9.7 12.5 -3.0": ["bombshells"], "1.6 10.6 3.9": ["holsters"], "-7.1 8.9 2.4": ["lesbianism"], "10.2 9.9 4.2": ["anagram"], "5.9 4.2 16.5": ["juicier"], "13.6 18.9 5.7": ["badlands"], "10.1 0.1 6.0": ["redid"], "2.1 2.8 8.7": ["ribald"], "15.2 7.0 24.4": ["geckos"], "19.4 1.8 6.1": ["onthe"], "-1.7 4.8 7.2": ["shaper"], "7.6 13.3 4.3": ["throttles"], "3.1 7.5 15.7": ["bistros"], "1.7 13.3 14.1": ["nigga"], "8.0 8.9 4.6": ["pornographers"], "-6.3 14.2 -1.0": ["speechwriters"], "0.8 8.8 19.7": ["wushu"], "-3.7 -1.6 3.6": ["educationists"], "10.5 6.9 1.6": ["harangued"], "6.6 4.7 9.7": ["xenon"], "-6.5 7.6 2.9": ["epinephrine"], "6.6 6.3 28.0": ["warbler"], "6.8 -1.0 11.9": ["lunchboxes"], "-2.0 4.0 0.4": ["trusteeship"], "11.0 1.1 31.0": ["flan"], "-1.0 11.8 16.5": ["outdoorsmen"], "-0.3 15.0 0.6": ["postulate"], "6.4 12.7 5.4": ["inclines"], "4.2 16.6 12.1": ["drunkard"], "5.3 4.2 1.3": ["gurdwara"], "1.4 1.0 13.6": ["sachet"], "9.4 9.5 13.3": ["sours"], "8.6 7.4 4.6": ["obviousness"], "-0.3 13.6 7.0": ["diphtheria"], "4.4 11.7 10.5": ["newsgroups"], "2.4 6.7 8.4": ["geographer"], "-0.9 0.2 4.7": ["neuromuscular"], "11.1 5.5 18.9": ["tufts"], "-4.1 2.9 28.5": ["roti"], "19.0 9.3 3.9": ["belch"], "1.9 2.6 4.8": ["throaty"], "8.3 5.8 4.7": ["deflates"], "5.5 5.7 18.3": ["emeralds"], "10.1 8.0 4.5": ["retinas"], "11.2 9.8 16.3": ["choicest"], "0.7 11.6 3.6": ["deciders"], "6.2 4.0 1.7": ["voluble"], "0.6 4.6 7.8": ["lawyering"], "-4.6 15.5 9.3": ["neutrophils"], "-1.4 6.1 10.7": ["tithing"], "1.5 4.2 7.5": ["sellable"], "14.2 4.9 9.8": ["portentous"], "8.4 2.9 8.3": ["rimonabant"], "3.8 -2.5 7.1": ["tripleheader"], "6.7 11.0 15.0": ["gonzo"], "7.5 6.5 4.8": ["bagpiper"], "-11.4 5.0 3.1": ["rbi"], "-3.1 4.5 11.3": ["mezzo"], "-6.6 11.7 -4.3": ["operationalized"], "11.6 7.6 -0.6": ["moviemaker"], "-0.2 11.2 9.5": ["adenovirus"], "-5.3 11.5 1.5": ["mobilizations"], "-1.3 10.5 3.3": ["deleverage"], "-1.0 11.1 24.6": ["sandbars"], "8.6 2.7 5.0": ["rewired"], "10.5 8.3 12.8": ["vagrant"], "6.2 9.8 3.4": ["blinder"], "9.2 12.1 31.5": ["lichen"], "-0.3 5.5 0.8": ["solubility"], "-13.8 5.2 4.7": ["relapsing"], "-4.9 5.9 10.4": ["pixantrone"], "-1.9 11.3 17.3": ["chaparral"], "-6.6 2.5 0.7": ["unexpired"], "10.7 1.4 5.1": ["jackknifed"], "25.6 18.5 9.4": ["primeval"], "8.7 4.2 12.5": ["tutus"], "8.3 2.5 12.3": ["reauthorizing"], "14.9 8.9 12.2": ["torpor"], "20.0 25.2 10.0": ["droid"], "8.7 7.4 18.1": ["ices"], "2.2 -2.1 8.2": ["coiffed"], "1.2 2.4 6.6": ["preemies"], "1.9 3.3 21.0": ["nosh"], "-3.3 17.4 6.7": ["toleration"], "5.0 12.7 15.0": ["wiper"], "-3.2 9.9 11.9": ["vancomycin"], "10.0 -0.4 5.9": ["tampons"], "5.1 12.9 7.6": ["subgenre"], "1.0 3.7 1.5": ["cleanroom"], "-2.5 6.9 9.2": ["freeroll"], "-5.7 0.6 -3.5": ["laudatory"], "-5.9 -3.4 11.4": ["farrier"], "-4.5 7.4 4.9": ["recollected"], "-1.9 9.5 4.5": ["deregistration"], "1.9 -0.8 9.6": ["lats"], "-2.5 11.1 -3.8": ["unrewarded"], "12.6 9.6 2.0": ["molehill"], "-5.8 5.3 11.7": ["shiraz"], "7.2 -4.7 8.9": ["suk"], "2.7 1.0 8.2": ["phaseout"], "3.3 4.0 5.6": ["grilles"], "10.7 8.1 4.5": ["exultant"], "-6.9 11.7 -0.6": ["defilement"], "7.5 3.6 11.9": ["clumping"], "8.3 16.4 11.1": ["spreaders"], "-5.3 7.5 4.8": ["ejaculation"], "5.2 10.5 26.6": ["netters"], "9.4 13.5 4.8": ["abysmally"], "-2.5 12.5 3.4": ["subregion"], "-6.6 5.9 4.8": ["lidocaine"], "1.6 1.8 7.7": ["debauched"], "4.1 3.7 9.2": ["filmic"], "10.5 20.3 12.5": ["exceptionalism"], "10.6 20.0 17.6": ["pox"], "1.7 8.2 7.7": ["ri"], "6.2 6.8 0.2": ["suffices"], "1.8 13.0 9.2": ["chikungunya"], "9.8 12.4 6.5": ["witless"], "-3.5 6.6 -1.1": ["spaciousness"], "1.3 15.2 3.2": ["cordoned"], "12.6 8.0 17.1": ["dom"], "6.8 30.0 3.1": ["warmonger"], "4.4 5.6 31.9": ["buckwheat"], "8.8 5.1 5.6": ["quattro"], "5.2 13.7 16.4": ["catchable"], "-4.7 7.3 3.8": ["unconformity"], "-1.8 9.6 6.2": ["octroi"], "4.7 3.2 0.5": ["ethnographic"], "-6.1 20.7 12.4": ["dharma"], "5.3 -0.6 -3.4": ["computerize"], "0.9 3.1 -2.1": ["debited"], "12.5 10.3 3.4": ["reimagined"], "-3.4 25.6 3.8": ["ember"], "4.9 2.2 7.7": ["unsubsidized"], "2.0 7.0 24.0": ["falconry"], "5.3 0.7 8.8": ["assemblages"], "2.8 7.0 10.7": ["gaiety"], "22.0 14.2 11.9": ["netherworld"], "2.7 10.4 14.5": ["albinos"], "3.7 10.8 11.6": ["nanowire"], "8.1 5.1 4.2": ["odes"], "-11.0 -2.4 12.9": ["avails"], "8.9 13.8 17.7": ["ocher"], "-6.6 16.9 10.4": ["homecomings"], "-2.7 12.0 7.0": ["deforested"], "9.1 8.6 9.5": ["guttural"], "8.5 8.8 15.5": ["coppers"], "13.7 2.7 8.9": ["getup"], "3.7 5.6 27.8": ["blanched"], "8.6 22.6 13.6": ["trespasser"], "-7.1 5.5 9.8": ["takaful"], "11.3 10.7 16.4": ["moccasins"], "3.0 8.9 0.3": ["circulations"], "1.7 2.6 8.1": ["kinetics"], "3.5 8.4 0.0": ["riling"], "-1.7 4.0 1.4": ["uncompensated"], "3.0 0.5 5.7": ["ayurvedic"], "2.8 5.7 9.2": ["bolivars"], "9.2 -0.9 3.1": ["perking"], "-5.6 6.8 8.9": ["bisexuality"], "8.5 3.2 -4.0": ["das"], "-3.0 6.8 4.9": ["baptismal"], "-0.9 7.7 -3.7": ["whistleblowing"], "-7.7 0.2 4.7": ["classwork"], "0.4 9.6 4.6": ["wanderings"], "10.8 14.8 9.6": ["wasters", "jokefest"], "6.8 3.1 3.5": ["incidentals"], "4.9 26.9 7.4": ["noblest"], "8.1 10.7 13.4": ["stowaways"], "0.4 6.7 12.3": ["shuttlers"], "-1.2 21.6 10.8": ["progressivism"], "-4.2 18.8 35.1": ["muskies"], "5.5 3.9 6.3": ["scandalously"], "11.7 8.2 5.3": ["coexisting"], "2.1 1.6 2.0": ["retinopathy"], "3.7 19.7 4.3": ["certitude"], "14.3 4.6 23.8": ["doughy"], "3.3 10.1 8.2": ["hitchhike"], "-4.3 6.9 6.8": ["bunking"], "-7.9 25.3 -0.5": ["insubordinate"], "-1.5 12.5 -1.4": ["transpiring"], "13.3 5.9 18.3": ["snouts"], "5.1 2.3 0.9": ["yeas"], "27.7 13.9 22.9": ["armadillo"], "-0.3 23.8 10.2": ["atheistic"], "3.1 4.1 3.7": ["guestroom"], "3.5 10.3 -0.2": ["intimating"], "7.8 2.4 7.4": ["tu"], "-1.6 5.7 3.9": ["temperance"], "2.9 0.8 26.4": ["curd"], "1.1 -0.8 6.5": ["reoccur"], "-6.6 5.7 8.2": ["shapers"], "-0.4 8.8 6.9": ["satraplatin"], "3.3 5.3 -1.4": ["dramatizes"], "10.5 6.8 6.8": ["impregnating"], "6.5 12.3 -1.5": ["stablemates"], "-3.9 23.8 4.6": ["comradeship"], "5.8 10.8 11.2": ["centerman"], "2.0 10.0 3.6": ["jobsite"], "1.5 0.2 4.8": ["chromatography"], "15.9 12.2 1.7": ["chumps"], "2.2 1.7 31.0": ["romaine"], "4.8 21.4 8.4": ["doublespeak"], "5.7 2.9 27.4": ["eggplants"], "-5.5 11.4 6.0": ["reoccupied"], "6.9 9.8 7.5": ["exploitive"], "-0.8 9.4 11.5": ["unbuttoned"], "1.8 4.8 6.5": ["obit"], "8.5 -1.4 0.5": ["percolated"], "-1.2 6.6 1.5": ["infirmities"], "7.5 6.8 9.2": ["mothballing"], "-1.8 4.9 -6.9": ["maintainable"], "13.1 9.6 10.5": ["farting"], "0.8 21.8 7.5": ["humanly"], "14.8 4.5 4.0": ["backflips"], "9.8 6.0 -1.4": ["patentability"], "1.7 6.3 1.5": ["roadtrip"], "9.5 18.1 7.6": ["imposters"], "-2.4 -3.9 1.3": ["backgrounder"], "9.7 10.1 9.9": ["cartwheel"], "20.0 9.6 -0.3": ["crumpling"], "-3.0 20.8 -0.1": ["bugler"], "-8.0 5.8 7.1": ["trastuzumab"], "-0.9 12.2 6.0": ["outrebound"], "20.0 14.7 11.7": ["skullduggery"], "0.7 4.8 -6.0": ["violative"], "1.8 12.7 8.7": ["exportable"], "11.9 11.5 6.2": ["scrunched"], "3.2 11.8 -0.7": ["trivializing"], "-2.3 9.9 12.1": ["cerebellum"], "1.3 7.5 2.1": ["vexatious"], "1.8 13.6 21.7": ["crossbows"], "12.5 4.7 4.2": ["squelching"], "-6.7 11.7 2.7": ["heterosexuality"], "4.8 4.5 11.7": ["shoelace"], "1.1 10.8 19.8": ["appropriators"], "5.4 6.3 61.5": ["anchovy"], "-5.2 13.6 1.8": ["messaged"], "0.1 6.1 25.5": ["vino"], "13.9 11.2 7.2": ["swats"], "10.3 9.5 15.1": ["moistened"], "0.2 9.9 3.4": ["affinities"], "6.6 6.0 16.1": ["waistcoat"], "3.6 12.6 1.1": ["ribosome"], "0.8 6.5 4.7": ["perforations"], "8.2 11.8 9.2": ["softballs"], "4.0 14.3 9.3": ["carjack"], "5.7 8.5 11.4": ["png"], "3.2 2.8 2.1": ["unsealing"], "6.9 -1.0 29.4": ["fritters"], "-4.2 -2.1 8.6": ["cleanings"], "7.8 5.4 17.3": ["ken"], "13.4 6.2 25.2": ["unappetizing"], "7.9 2.1 10.5": ["hydrates"], "-4.6 0.4 -1.8": ["costarred"], "1.9 20.4 8.4": ["perishing"], "-12.5 -3.6 6.8": ["overnights"], "-0.2 12.8 3.0": ["cleverer"], "16.7 1.2 2.0": ["spinout"], "-2.4 8.4 6.0": ["deicing", "etfs"], "0.7 -0.3 2.7": ["modulators"], "9.3 9.8 3.0": ["discotheque"], "22.1 12.0 15.2": ["inky"], "0.6 9.3 6.9": ["soundings"], "4.8 9.4 6.8": ["ballers"], "10.5 4.1 13.2": ["david"], "9.5 4.2 8.3": ["unburdened"], "1.5 15.9 12.6": ["frontmen"], "11.2 -0.7 2.5": ["newsflow"], "3.3 0.9 11.4": ["gentrified"], "-6.7 6.6 0.7": ["derailments"], "14.0 17.7 13.4": ["eddies"], "9.5 17.6 9.2": ["watchmen"], "4.2 11.1 9.0": ["fending"], "-1.8 1.3 14.5": ["pb"], "5.0 2.7 13.6": ["snipping"], "9.1 3.0 2.1": ["unionizing"], "9.7 10.0 11.4": ["undifferentiated"], "8.0 20.1 10.5": ["manliness"], "5.1 10.3 21.9": ["icebreakers", "defrosting"], "15.0 9.7 42.5": ["barnacles"], "3.1 7.0 10.2": ["botanists"], "4.9 4.6 3.0": ["rededicate"], "8.7 5.5 -0.5": ["slouched"], "-1.9 3.6 11.2": ["knead"], "-3.2 8.9 0.4": ["persistency"], "7.3 7.2 7.0": ["cedes"], "1.5 6.0 29.0": ["grog"], "3.4 4.0 4.3": ["sigma"], "8.3 13.8 8.8": ["retards"], "4.6 3.8 3.5": ["schoolbooks"], "9.7 2.7 12.2": ["mantelpiece"], "-2.2 3.6 6.7": ["subwoofers"], "-14.2 7.8 10.0": ["undesignated"], "3.0 11.6 21.4": ["chrysanthemums"], "6.9 10.4 7.9": ["megachurches"], "1.5 25.3 -1.3": ["unflinchingly"], "8.5 6.0 9.3": ["throught"], "1.2 8.9 3.2": ["reconfigurable"], "3.9 24.2 5.2": ["agressive"], "18.3 6.2 9.0": ["teddy"], "-7.1 3.2 7.4": ["podcasters"], "7.7 11.6 8.9": ["goofs"], "10.4 7.1 13.2": ["armoire"], "13.5 -1.6 12.1": ["latin"], "-18.0 0.5 9.8": ["homesites"], "8.1 10.1 6.9": ["scarily"], "18.7 3.6 11.8": ["swill"], "-2.9 8.6 42.4": ["morels"], "-11.3 2.8 3.7": ["outpolled"], "-2.0 15.1 22.6": ["fescue"], "9.5 14.7 8.7": ["backstops"], "-2.8 3.2 1.3": ["felicitation"], "7.2 8.3 14.6": ["stiletto"], "8.5 18.7 9.0": ["polygons"], "14.0 15.5 0.6": ["satnav"], "5.4 3.0 6.6": ["aw"], "13.1 -2.1 20.8": ["shimmery"], "14.9 7.0 10.1": ["scraggly"], "1.2 10.7 0.9": ["matchwinner"], "5.2 -5.1 6.1": ["ea"], "-0.3 6.8 15.3": ["sarong"], "-7.2 5.6 2.8": ["cantata"], "-6.0 0.7 3.8": ["investiture"], "0.8 5.3 15.4": ["cottonseed"], "-6.2 6.1 -6.5": ["educative"], "11.6 4.2 6.9": ["undertakers"], "9.9 6.5 4.6": ["mutterings"], "9.0 17.7 3.3": ["gullibility"], "-11.9 -1.2 1.0": ["collegiately"], "15.3 6.9 20.8": ["cornflakes"], "8.7 18.3 4.8": ["verboten"], "2.7 3.4 0.7": ["biofeedback"], "7.0 15.3 6.8": ["rashly"], "-4.0 7.4 11.5": ["spectrums"], "5.4 6.5 10.0": ["womanly"], "-1.7 -5.7 5.6": ["retrospectives"], "-9.6 -1.7 6.4": ["umpired"], "7.0 14.9 7.2": ["spikers"], "-0.0 1.1 11.5": ["casuals"], "-7.8 9.0 0.2": ["erudition"], "17.3 2.1 12.3": ["dodo"], "-2.2 -2.8 19.5": ["cheesecakes"], "15.4 5.7 9.0": ["teems"], "16.9 8.8 8.0": ["flutters"], "11.5 9.8 14.4": ["pirouette"], "11.4 7.5 6.3": ["edifices"], "0.3 0.2 8.1": ["unwed"], "-0.8 5.2 1.0": ["recalibration"], "3.4 4.8 12.4": ["tailgates"], "12.0 13.1 0.2": ["clasping"], "3.2 3.4 -8.7": ["testaments"], "11.0 7.2 2.4": ["downhole"], "6.0 7.4 0.9": ["supranational"], "8.5 6.5 4.0": ["reemerged"], "5.8 8.8 3.0": ["cocooned"], "3.3 0.9 0.5": ["hypoallergenic"], "6.0 11.5 7.7": ["ligand"], "3.2 12.0 4.4": ["funnest"], "-3.0 10.7 21.5": ["cayenne"], "-0.6 8.6 8.9": ["plagiarizing"], "1.7 8.8 12.5": ["collocation"], "-3.0 -0.3 10.7": ["finasteride"], "9.8 -3.0 0.5": ["slimline"], "3.9 11.9 9.4": ["hoarder"], "-6.0 10.9 10.6": ["footwall"], "5.7 15.6 11.1": ["loners"], "4.4 4.8 10.5": ["screwy"], "4.1 6.2 4.3": ["asbestosis"], "9.1 2.6 10.3": ["boxcar"], "7.8 25.9 4.5": ["nobly"], "14.1 10.2 7.9": ["thermos"], "-1.1 12.4 6.0": ["secularization"], "10.0 10.4 6.9": ["apogee"], "7.6 17.4 4.3": ["unswerving"], "-6.8 2.2 5.9": ["peerages"], "8.6 4.0 1.9": ["pulsar"], "-0.9 0.1 -1.2": ["attestation"], "0.6 4.7 8.8": ["retreads"], "4.8 6.0 31.8": ["ospreys"], "15.0 2.6 1.2": ["backrower"], "-1.6 12.8 -0.7": ["detoxify"], "6.3 2.4 10.4": ["prissy"], "0.1 6.7 4.3": ["condenses"], "0.8 -6.1 3.0": ["fidgeted"], "6.0 7.9 27.7": ["macaques"], "-1.3 1.1 22.1": ["biscotti"], "-4.9 0.6 16.4": ["malts"], "13.1 6.5 33.1": ["partridge"], "10.6 -0.5 3.0": ["unwinds"], "2.2 8.6 12.4": ["leptospirosis"], "5.1 8.0 -0.3": ["besmirched"], "2.3 9.5 5.0": ["junctures"], "-1.5 3.2 -1.4": ["interdenominational"], "2.0 4.8 5.5": ["sluts"], "-8.9 -2.3 2.0": ["rostered"], "-2.6 9.9 2.6": ["transmissible"], "11.0 7.6 30.4": ["tapioca"], "-0.2 10.9 10.5": ["nightwatchman"], "2.1 25.0 7.7": ["pacification"], "8.7 11.4 13.8": ["feathering"], "1.7 -2.5 11.2": ["beadwork"], "5.5 4.4 8.4": ["distiller"], "12.4 19.4 17.2": ["hyena"], "1.9 9.7 -1.2": ["plights"], "1.5 11.1 20.8": ["cultivators"], "1.5 6.3 20.4": ["marinating"], "11.8 10.5 10.2": ["turner"], "-9.7 7.4 1.8": ["defragmentation"], "4.9 0.9 7.9": ["pieced"], "15.0 7.4 -0.7": ["flashiest"], "0.4 4.4 36.6": ["shrimper"], "-2.5 4.4 13.3": ["downslide"], "5.4 14.0 -1.4": ["seatback"], "0.9 18.2 27.7": ["hostas"], "5.5 11.7 5.5": ["discombobulated"], "-1.7 -6.2 7.7": ["folio"], "-3.2 35.8 5.0": ["aircrews"], "15.4 27.0 15.7": ["howitzer"], "9.1 3.3 18.2": ["bayfront"], "9.8 3.1 14.5": ["smock"], "8.2 6.1 5.7": ["outgaining"], "13.8 7.3 9.3": ["lovesick"], "9.6 11.9 11.1": ["surer"], "4.6 10.0 10.0": ["yelping"], "14.1 6.9 12.1": ["dimwitted"], "-3.4 9.9 3.0": ["stammered"], "2.6 20.9 -1.0": ["disengaging"], "8.5 6.6 4.8": ["fondest"], "-1.0 2.9 37.7": ["chard"], "7.6 5.3 6.5": ["bathes"], "9.2 15.3 9.7": ["flagstick"], "-1.4 8.2 4.5": ["connived"], "15.3 9.3 10.0": ["stank"], "8.8 18.7 6.3": ["exhaling"], "-1.8 5.9 10.1": ["retransmission"], "-8.3 1.7 9.9": ["inhalants"], "-3.7 0.2 5.4": ["woodwind"], "5.7 1.3 -0.6": ["doffed"], "5.0 9.5 -0.3": ["reconnects"], "11.4 22.3 3.7": ["cultists"], "7.1 6.7 8.2": ["dey"], "1.0 8.9 10.4": ["hale"], "2.8 -0.1 6.5": ["saxophones"], "-2.7 19.2 8.1": ["peaceable"], "12.1 5.8 21.2": ["porcine"], "-0.6 13.7 14.4": ["prequels"], "14.0 11.9 14.8": ["doormats"], "2.1 13.7 14.8": ["tigress"], "-3.0 0.4 9.5": ["clubman"], "9.4 29.1 3.4": ["malevolence"], "4.9 -0.8 4.1": ["cine"], "5.0 4.3 8.0": ["bolivar"], "-5.1 11.5 7.6": ["outraised"], "-0.2 14.5 3.6": ["immunizing"], "9.8 5.6 0.6": ["ect"], "13.1 4.7 3.4": ["tames"], "4.9 8.9 -1.6": ["situate"], "-2.4 22.2 5.9": ["uncivil"], "5.7 3.9 2.6": ["biosensor"], "0.2 5.5 26.4": ["pastrami"], "5.7 13.7 10.6": ["slants"], "-2.5 1.5 3.0": ["impulsivity"], "6.6 14.8 0.4": ["broadsides"], "3.0 -0.5 -0.4": ["invalidates"], "-0.6 2.5 3.6": ["preflight"], "5.8 24.0 13.9": ["bloodlust"], "6.1 15.9 17.3": ["yelps"], "8.2 10.5 9.7": ["fetishes"], "14.8 9.6 15.2": ["fanciest"], "4.2 1.9 6.7": ["kw"], "6.4 16.0 13.2": ["tagger"], "31.9 9.9 14.6": ["animatronic"], "10.8 11.1 8.9": ["counterclockwise"], "0.1 15.7 7.7": ["aloofness"], "14.6 4.4 11.9": ["willowy"], "2.9 10.6 11.1": ["wack"], "-8.5 11.4 -0.1": ["ulema"], "0.6 12.9 20.8": ["broods"], "-9.4 -0.4 1.9": ["obstetrical"], "-0.2 6.0 6.3": ["churchmen"], "-3.9 7.7 7.1": ["disconnections"], "3.5 2.6 9.5": ["telecasting"], "15.5 17.7 5.6": ["airships"], "0.2 8.0 7.6": ["heeds"], "1.4 3.8 -1.8": ["jinked"], "13.2 3.9 8.9": ["faceted"], "4.3 2.0 13.8": ["pullover"], "-3.8 -2.6 3.5": ["grandfathering"], "5.0 2.7 2.0": ["forgoes"], "11.1 11.5 2.8": ["cleverest"], "13.3 13.9 4.4": ["orifice"], "6.0 9.4 9.1": ["patriarchs"], "9.3 0.4 14.3": ["duller"], "-2.7 5.4 1.5": ["editorialists"], "3.7 4.6 3.6": ["linguistically"], "11.3 3.0 6.8": ["va"], "4.0 13.6 20.9": ["seasick"], "2.4 0.5 4.3": ["gravitating"], "3.6 -2.3 0.3": ["laundries"], "2.5 7.6 4.1": ["undock"], "3.3 6.5 11.2": ["hydrothermal"], "7.1 7.1 4.1": ["colas"], "7.4 16.1 5.8": ["nav"], "3.8 1.3 4.7": ["incontinent"], "15.6 0.9 13.3": ["droopy"], "23.6 11.5 20.2": ["marsupial"], "2.0 19.3 1.7": ["renounces"], "10.1 -3.7 7.2": ["une"], "4.6 -0.3 15.2": ["corduroy"], "7.8 5.7 -2.1": ["analogs"], "5.8 5.1 13.2": ["belter"], "2.3 9.6 13.2": ["lugs"], "6.4 10.1 16.5": ["indentation"], "3.0 3.7 7.5": ["spacer"], "5.3 11.2 6.5": ["sharecropper"], "2.6 12.2 18.4": ["aperitif"], "14.5 17.6 7.5": ["misbegotten"], "-4.6 -4.0 0.8": ["oversubscription"], "0.5 3.4 15.4": ["sheetrock"], "-7.1 11.7 8.1": ["nonnegotiable"], "7.9 11.9 23.9": ["mesquite"], "-3.3 6.7 9.0": ["uninsurable"], "6.9 11.0 11.3": ["itis"], "9.5 18.0 6.1": ["unwelcoming"], "13.5 3.2 3.0": ["stewardesses"], "-8.3 2.4 13.6": ["milers"], "-7.3 5.0 9.7": ["estrogens"], "19.2 13.0 9.9": ["eyeballing"], "-0.2 7.5 -1.6": ["switchbacks"], "9.3 21.1 28.3": ["gobblers"], "21.2 11.6 -3.7": ["oligopoly"], "8.8 13.5 7.7": ["manhandle"], "-5.1 2.9 7.0": ["deadlocks"], "-3.6 4.7 1.5": ["flexibilities"], "19.8 19.2 3.5": ["immensity"], "-2.8 9.3 4.4": ["prude"], "0.4 9.7 8.4": ["quipping"], "13.7 9.8 5.1": ["alphabets"], "8.6 11.9 1.9": ["fortuitously"], "14.2 -3.6 7.5": ["moo"], "6.8 5.0 0.1": ["intellibitz"], "0.5 -2.2 2.6": ["pas"], "1.4 -2.5 3.4": ["heydays"], "1.7 7.5 16.8": ["hiphop"], "17.4 6.8 20.1": ["purloined"], "10.1 14.8 18.5": ["splotches"], "-10.3 4.6 3.5": ["rereading"], "3.1 10.1 8.3": ["winces"], "15.0 2.8 4.9": ["affixing"], "3.1 -7.9 8.8": ["dieticians"], "0.3 8.9 -5.7": ["disrobe"], "6.8 11.0 11.1": ["credulous"], "8.6 -0.3 6.8": ["hollywood"], "4.8 4.2 3.9": ["livin"], "-0.6 3.6 0.7": ["radiography"], "9.0 -8.0 15.7": ["cms"], "0.4 5.1 14.7": ["metallics"], "-2.4 13.0 0.3": ["reintegrated"], "9.3 9.6 12.3": ["bollocks"], "-9.3 15.4 2.0": ["unimproved"], "10.8 9.2 9.2": ["refitting"], "4.2 1.5 14.4": ["spars"], "2.2 3.6 19.3": ["phlegm"], "8.5 27.9 7.4": ["pitiless"], "10.4 14.5 4.9": ["futilely"], "8.6 10.8 11.3": ["funereal"], "-7.5 8.6 5.1": ["alleles"], "12.7 -1.3 8.8": ["sheaf"], "4.2 2.4 7.3": ["distributable"], "14.3 14.9 11.1": ["withers"], "0.6 1.4 3.9": ["shod"], "-4.2 7.6 -4.7": ["helpfulness"], "8.7 5.2 6.1": ["yall"], "13.9 -6.9 -0.5": ["packager"], "7.8 9.8 2.6": ["furrow"], "-10.3 -2.6 1.7": ["signoff"], "5.6 2.0 1.6": ["ombudsmen"], "-2.7 18.4 5.2": ["dispensable"], "20.2 12.2 12.1": ["fruitlessly"], "6.5 8.6 2.4": ["crosswords"], "4.2 20.5 -1.0": ["neutralizes"], "14.2 26.2 -0.6": ["vanquishing"], "-1.5 13.8 3.4": ["doctrinaire"], "15.3 20.2 14.6": ["immortals"], "4.5 11.0 2.4": ["honks"], "9.3 9.0 6.8": ["quizzical"], "9.6 16.8 10.7": ["daylights"], "13.2 9.6 5.4": ["consumerist"], "17.0 1.9 6.6": ["overpricing"], "-1.1 -1.1 2.5": ["annulling"], "4.5 4.7 19.4": ["thatched"], "4.1 12.9 3.2": ["clickers"], "8.5 7.8 4.8": ["burnishing"], "3.4 0.9 7.7": ["slumming"], "5.3 10.8 9.2": ["kith", "acclimatises"], "-4.4 13.4 -0.6": ["dangerousness"], "10.6 1.6 -2.8": ["lastest"], "-3.8 32.3 6.7": ["servicemember"], "9.9 12.7 -3.4": ["catalyzing"], "-0.7 44.0 5.9": ["recon"], "10.7 4.4 6.1": ["chiselled"], "12.0 3.0 13.0": ["tumblers"], "4.4 5.1 2.6": ["dummied"], "5.3 4.4 5.6": ["methyl"], "-4.0 3.2 8.1": ["retouching"], "1.7 -1.2 -0.6": ["imeem"], "1.6 4.1 9.2": ["shoplift"], "-1.7 9.3 3.1": ["actuation"], "0.2 12.8 10.1": ["stinkers"], "-1.0 29.5 3.7": ["civilizational"], "10.5 22.0 2.8": ["telepathic"], "5.8 24.7 2.3": ["unifier"], "-10.6 10.0 4.2": ["exacerbations"], "-7.7 8.6 14.1": ["sputum"], "16.1 6.2 13.7": ["wrinkly"], "1.1 13.1 -2.5": ["tribulation"], "11.4 -0.3 6.2": ["packagers"], "1.1 14.9 33.3": ["breading"], "14.2 7.7 3.8": ["multifarious"], "16.9 7.1 5.9": ["unwrapping"], "2.5 12.8 12.6": ["inswinger"], "10.7 10.4 9.6": ["chokers"], "-0.5 4.7 10.7": ["splitters"], "0.1 4.5 41.6": ["fingerlings"], "2.8 10.4 8.8": ["indolent"], "7.8 7.8 7.5": ["workroom"], "4.2 14.4 5.5": ["jailbroken"], "-3.9 9.8 14.4": ["hypervisors"], "14.6 4.6 9.6": ["whiteboards"], "11.8 3.6 0.1": ["comedown"], "5.9 -2.9 7.9": ["partook"], "6.9 16.4 24.7": ["cattails"], "2.0 11.1 10.8": ["homesteaders"], "1.4 11.6 13.6": ["guesstimate"], "10.5 1.4 6.9": ["cutaway"], "7.0 10.0 20.2": ["boobies"], "9.1 11.9 7.7": ["steppes"], "7.5 17.8 25.1": ["flukes"], "-1.0 2.7 8.6": ["dumpsite"], "-2.5 3.4 -1.2": ["grassroot"], "13.5 -2.0 6.9": ["jukeboxes", "bodywash"], "5.6 -1.9 15.6": ["bullfights"], "7.0 11.3 13.0": ["rottweiler"], "12.1 14.3 4.2": ["loneliest"], "-2.3 10.6 1.9": ["nailbiter"], "-0.3 3.9 5.3": ["tailpipes"], "15.3 5.4 12.0": ["girdle"], "-1.3 17.5 14.2": ["mayday"], "7.3 3.5 15.4": ["spoonfuls"], "0.6 9.2 6.0": ["desegregated"], "10.9 8.8 12.6": ["farmyard"], "2.4 2.8 5.7": ["bunds"], "-9.6 3.7 4.9": ["motos"], "9.3 5.8 12.3": ["lobes"], "46.7 16.1 28.2": ["leviathan"], "4.5 10.1 8.2": ["cagers"], "-4.3 6.4 3.7": ["restenosis"], "15.7 13.3 11.2": ["marionettes"], "23.0 21.0 22.4": ["weasels"], "7.6 12.3 3.8": ["fogged"], "2.8 7.2 16.7": ["cymbal"], "5.2 2.7 11.8": ["groupware"], "-5.9 1.0 7.3": ["beneficiation"], "10.2 32.4 3.7": ["pursuer"], "19.4 14.0 9.6": ["monstrously"], "6.7 2.9 21.1": ["barbell"], "4.5 14.6 22.9": ["sloop"], "-3.5 -1.3 -0.7": ["outrighted"], "8.3 10.6 13.5": ["cartography"], "-6.4 1.7 5.1": ["lathicharge"], "6.2 23.1 15.7": ["steed"], "1.8 -0.8 12.1": ["sharps"], "7.8 10.9 -0.9": ["derides"], "8.9 2.7 -2.8": ["headrests"], "2.6 8.1 3.7": ["dumbstruck"], "4.9 7.5 7.1": ["wishful"], "7.1 10.2 11.5": ["coalmine"], "3.4 3.4 8.3": ["biodegrade"], "23.4 4.2 -0.2": ["mockup"], "4.4 7.7 20.2": ["euchre"], "0.8 14.2 20.9": ["bilge"], "18.1 21.2 14.2": ["metaphoric"], "2.2 11.1 3.4": ["nitro"], "-10.4 13.0 11.6": ["imatinib"], "-2.7 7.0 5.9": ["wakefulness"], "-6.6 6.3 0.3": ["costumer"], "12.3 -0.7 5.9": ["smallcap"], "-6.7 15.1 7.5": ["southerner"], "10.9 12.5 21.5": ["winches"], "2.2 5.0 1.9": ["rockier"], "15.9 3.8 1.2": ["careering"], "6.2 15.1 5.7": ["factoid"], "24.5 5.1 28.4": ["styrofoam"], "7.9 19.8 12.2": ["neurosis"], "3.5 22.3 3.6": ["provocateurs"], "3.2 12.8 6.5": ["jlitke"], "-5.8 9.9 -2.4": ["disassociate"], "23.0 28.9 12.8": ["slayer"], "5.5 -1.1 -3.4": ["nanoelectronics"], "10.1 4.8 -1.3": ["softwares"], "-2.2 5.5 3.9": ["occlusion"], "0.3 12.7 7.7": ["undercapitalized"], "-6.9 8.3 7.0": ["designees"], "-2.9 -0.4 23.8": ["kava"], "-0.5 6.0 6.1": ["inflections"], "5.4 1.2 7.9": ["london"], "-8.9 9.4 6.2": ["lymphomas"], "5.8 6.4 10.9": ["unwholesome", "overamplified"], "9.6 18.4 5.9": ["bewitched"], "8.1 5.1 28.5": ["fjord"], "10.1 8.3 11.0": ["metallers"], "13.9 7.8 2.4": ["franchiser"], "13.1 13.6 4.6": ["noisiest"], "1.1 7.3 5.8": ["bicameral"], "5.2 9.0 24.1": ["cyanobacteria"], "12.2 7.6 3.3": ["stowing"], "4.0 9.1 7.5": ["kindhearted"], "5.5 -2.5 -4.0": ["mobi"], "-2.3 13.2 15.5": ["hetero"], "12.8 6.5 19.6": ["scissor"], "7.9 9.7 13.8": ["boozer"], "2.0 -0.6 2.8": ["ip"], "7.6 12.6 7.4": ["charades"], "4.9 1.7 9.0": ["joiner"], "6.9 17.4 2.1": ["marshall"], "0.8 22.3 6.7": ["mendacity"], "-1.4 2.0 11.9": ["diclofenac"], "9.3 4.8 12.5": ["crocked"], "10.5 7.6 11.4": ["prodigal"], "8.4 12.5 4.0": ["corroding"], "0.9 0.2 16.6": ["hispanic"], "6.5 4.1 54.1": ["conch"], "5.2 9.7 19.4": ["transom"], "13.8 10.1 6.8": ["karmic"], "5.3 12.2 13.1": ["atrophied"], "3.2 12.0 2.6": ["reductive", "prequarterfinal"], "9.2 2.6 1.2": ["lullabies"], "6.5 15.9 11.2": ["braggadocio"], "7.0 8.2 3.5": ["wasn"], "10.5 12.5 5.4": ["entangle"], "7.2 11.9 4.8": ["claptrap"], "-4.6 5.6 -4.4": ["paediatrics"], "4.6 14.7 9.9": ["subtracts"], "15.7 13.5 6.0": ["encyclopaedia"], "1.0 -0.9 12.6": ["blanch"], "1.3 9.6 8.8": ["tryin"], "7.3 -2.7 7.4": ["binned"], "2.9 -0.0 14.9": ["molars"], "7.9 14.1 8.0": ["slavishly"], "14.7 1.0 -1.5": ["peddles"], "-3.3 22.4 6.7": ["complainer"], "-1.8 11.1 1.1": ["declarative"], "15.5 1.2 12.0": ["flattish"], "0.6 19.0 5.4": ["obdurate"], "4.9 16.2 -4.4": ["defiling"], "4.8 11.3 10.0": ["canoodling"], "15.1 -1.4 8.4": ["caf"], "7.9 8.2 0.4": ["bravo"], "-4.5 4.2 2.6": ["aortic"], "-2.8 14.8 1.4": ["narrowness"], "14.0 -0.1 8.9": ["headdresses"], "1.7 6.1 14.7": ["folky"], "-1.0 5.1 5.2": ["ayurveda"], "10.8 7.0 13.7": ["ticklish"], "0.4 9.2 7.9": ["jocular"], "6.2 3.5 15.9": ["bullfight"], "-3.0 6.2 12.9": ["sarcoma"], "5.0 5.3 9.0": ["morphological"], "-3.2 10.3 5.2": ["overwrite"], "10.8 11.5 7.4": ["alarmists"], "13.2 10.8 31.5": ["larval"], "-1.9 1.4 5.2": ["excretion"], "1.6 6.3 11.7": ["gravelly"], "-2.9 10.3 5.2": ["standoffish"], "5.9 16.5 11.3": ["sunburns"], "21.4 15.0 28.1": ["bumblebee"], "-2.1 18.1 16.2": ["topspin"], "3.4 9.2 7.4": ["foremen"], "-9.0 2.3 -1.6": ["gk"], "0.1 18.8 8.1": ["escarpment"], "10.3 5.9 0.6": ["remover"], "-0.9 20.0 8.3": ["unlikable"], "0.3 10.1 6.7": ["profundity"], "2.9 2.9 16.3": ["unfrozen"], "-1.8 6.5 -4.9": ["disbandment"], "-7.6 22.1 4.8": ["persecutions"], "14.2 14.4 3.7": ["implodes"], "12.0 24.0 14.8": ["outmaneuver"], "8.9 15.9 8.1": ["balaclavas"], "0.0 14.1 0.9": ["airframes"], "19.5 12.2 5.4": ["preeminence"], "16.7 6.4 5.8": ["readymade"], "8.9 13.7 7.2": ["whos"], "20.0 1.4 7.0": ["tinier"], "-6.0 12.1 3.7": ["jelling"], "5.9 12.3 28.5": ["boars"], "-3.5 2.0 2.7": ["decongest"], "-9.0 11.9 -0.9": ["hesitations"], "0.7 -0.6 1.1": ["reissuing"], "-0.9 11.4 5.3": ["wets"], "11.4 0.8 5.9": ["ts"], "4.7 0.3 7.6": ["plex"], "-0.6 21.9 11.4": ["obstinacy"], "8.3 1.2 9.2": ["multilayer"], "10.7 -1.2 -3.1": ["neater"], "4.3 0.8 3.6": ["ointments"], "1.3 12.2 8.1": ["affectees"], "8.6 0.5 -1.8": ["piezoelectric"], "1.1 6.2 10.6": ["panty"], "4.4 2.6 10.3": ["bodega"], "-0.8 5.7 -4.0": ["reformulation"], "3.9 12.9 7.9": ["bracketing"], "-2.2 9.7 8.3": ["hydel"], "12.3 10.7 17.2": ["greenies"], "-0.8 14.4 9.4": ["declarer"], "-4.4 1.4 3.1": ["expirations"], "3.8 6.4 0.7": ["footfalls"], "6.9 9.7 9.5": ["divots"], "7.5 14.0 12.2": ["balling"], "2.6 2.2 5.4": ["lacs"], "4.3 14.3 4.6": ["fainter"], "1.9 11.3 9.6": ["buffoonery"], "13.3 11.6 14.9": ["juiciest"], "12.7 9.6 33.7": ["briny"], "-14.9 -9.6 5.1": ["buprenorphine"], "12.5 6.4 3.8": ["planeload"], "5.2 9.2 8.4": ["mooning"], "6.2 17.7 -0.5": ["bunkered"], "0.8 14.1 -1.7": ["discoverable"], "4.7 16.4 8.6": ["parochialism"], "6.8 4.3 12.6": ["tranny"], "0.7 11.8 7.7": ["camber"], "2.5 7.7 2.2": ["spiritualism"], "16.4 9.1 -2.0": ["biomedicine"], "7.2 5.3 29.3": ["nearshore"], "10.6 17.7 4.0": ["gloated"], "1.8 14.5 4.9": ["demobilize"], "12.7 7.3 16.6": ["eared"], "1.8 4.2 21.7": ["brocade"], "-4.7 7.3 -0.3": ["sonata"], "-3.0 3.6 3.1": ["ns"], "9.7 4.9 4.2": ["oo"], "-1.8 6.2 11.8": ["consumptive"], "8.4 16.3 -0.5": ["hellhole"], "15.1 4.2 26.8": ["piglet"], "-1.7 2.2 11.7": ["speedways"], "2.5 15.6 1.8": ["xiv"], "9.0 14.1 6.0": ["friendless"], "-4.0 4.3 25.3": ["clinker"], "2.7 21.9 0.5": ["underestimation"], "-0.7 -1.5 54.2": ["crabmeat"], "9.3 6.0 15.0": ["breakdancing"], "-0.3 5.8 18.7": ["ingot"], "-0.8 -1.3 7.2": ["appendices"], "5.1 11.7 4.4": ["consummating"], "-5.6 6.2 9.0": ["soldered"], "3.2 18.5 5.8": ["priori"], "3.6 12.1 3.4": ["angriest"], "11.6 14.7 6.7": ["pawing"], "9.4 26.3 8.9": ["heathen"], "10.4 9.3 14.1": ["panhandler"], "11.5 7.8 19.3": ["pallid"], "3.4 1.6 10.6": ["pf"], "-2.5 3.3 3.0": ["cloudiness"], "11.3 17.0 5.6": ["spammed"], "9.3 17.7 6.7": ["compasses"], "14.1 -4.2 8.2": ["gussied"], "-3.8 6.3 17.7": ["microbrews"], "15.2 32.1 10.9": ["brutes"], "23.5 20.5 6.8": ["inanimate"], "4.0 2.6 6.0": ["corona"], "-9.1 4.5 11.1": ["furloughing"], "10.5 3.5 0.8": ["traipse"], "12.9 4.1 -2.3": ["edutainment"], "-7.2 -3.1 1.0": ["presales"], "-1.0 4.8 3.7": ["overcoats"], "11.2 3.3 11.5": ["wheelie"], "3.1 2.6 8.6": ["seamstresses"], "4.2 -1.6 20.0": ["yan"], "1.0 8.2 9.0": ["vaginas"], "6.3 4.9 8.0": ["saner"], "5.2 -3.2 9.0": ["punky"], "-0.1 12.5 11.3": ["abortionists"], "0.6 11.0 11.0": ["stigmas"], "14.3 -3.0 11.3": ["doyenne"], "8.5 3.3 7.5": ["centerfold"], "6.4 16.1 9.1": ["photog"], "10.3 5.9 11.4": ["swatch"], "0.3 8.7 11.2": ["tankan"], "6.2 8.7 25.5": ["seawalls"], "7.3 13.1 9.8": ["mincemeat"], "13.0 11.9 6.9": ["stolid"], "-11.1 6.5 12.7": ["vodkas"], "12.2 -1.6 2.1": ["fessed"], "2.8 6.1 2.7": ["sharecroppers"], "-2.7 16.7 -8.9": ["instrumentality"], "8.8 13.3 11.0": ["partygoer"], "12.5 4.8 3.3": ["abounding"], "10.5 8.2 7.8": ["stereotypically"], "6.5 2.3 1.4": ["quiets"], "-3.8 5.5 -1.1": ["operability"], "7.0 7.1 6.2": ["muddying"], "12.2 7.5 8.9": ["datacentres"], "8.7 -2.9 9.8": ["nite"], "-2.8 18.0 10.8": ["gentile"], "-2.3 7.2 26.0": ["dahlias"], "5.2 27.7 4.7": ["detestable"], "6.3 11.4 11.0": ["bleakness"], "7.6 8.3 6.2": ["savviest"], "1.8 8.8 15.1": ["sepia"], "4.8 9.0 7.4": ["undercount"], "-6.4 11.5 9.5": ["playcalling"], "26.5 16.7 4.6": ["monopolist"], "5.6 15.4 9.5": ["piledriver"], "20.1 4.0 5.2": ["spluttering"], "3.1 -0.4 7.2": ["wen"], "2.3 16.8 -1.0": ["discredits"], "6.0 11.1 6.9": ["distro"], "-2.8 7.3 -4.7": ["remanufactured"], "7.2 8.5 25.3": ["algal"], "16.1 8.9 0.6": ["reshapes"], "0.7 5.0 10.3": ["nearfall"], "5.3 5.2 14.8": ["woodworker"], "12.4 2.3 22.8": ["oiling"], "0.3 2.3 9.0": ["slacked"], "22.5 20.0 13.3": ["pixelated"], "5.5 9.0 5.1": ["nonfood"], "-7.3 7.8 3.0": ["cognitively"], "15.4 -8.2 0.4": ["quintupled"], "11.9 10.9 -0.5": ["humanized"], "13.2 6.8 10.2": ["wonks"], "-0.6 15.2 7.4": ["hesitance"], "10.6 14.6 2.8": ["astound"], "1.9 11.2 4.9": ["thermodynamics"], "0.1 10.2 11.1": ["subcultures"], "-1.0 18.2 5.9": ["pitied"], "3.8 15.6 0.2": ["accumulative"], "1.6 5.3 4.5": ["histrionic"], "8.7 9.0 39.1": ["porpoises"], "-6.6 2.1 -0.9": ["chargesheeted"], "-6.2 9.6 13.7": ["tints"], "14.8 5.5 12.8": ["umbilical"], "1.9 12.6 10.0": ["shotmaking"], "7.1 20.5 9.2": ["antihero"], "19.4 5.0 16.7": ["waddle"], "2.6 -3.9 17.7": ["peyote"], "11.8 8.7 23.5": ["souffle"], "7.3 26.1 9.4": ["insolent"], "9.0 10.6 30.7": ["egrets"], "-1.4 8.0 14.7": ["stayers"], "15.8 11.6 13.5": ["roundhouse"], "-1.0 5.0 3.1": ["unexposed"], "-10.6 24.6 8.1": ["stressor"], "17.4 11.3 10.3": ["jackhammers"], "0.8 23.8 14.5": ["muskets"], "12.9 18.7 21.8": ["gophers"], "6.8 6.9 27.8": ["rattan"], "1.1 27.2 4.2": ["untruth"], "2.7 24.2 5.6": ["emboldens"], "-5.0 -2.7 4.3": ["listserv"], "10.8 5.9 4.4": ["frontwoman"], "6.3 21.8 3.9": ["unquestioning"], "5.9 18.3 8.7": ["lustful"], "9.4 5.6 6.6": ["bagpipers"], "4.2 22.2 14.8": ["speeder"], "-2.7 19.9 4.1": ["dissidence"], "-0.6 6.0 5.1": ["intermissions"], "-4.0 11.3 0.9": ["provable"], "7.9 7.1 9.8": ["flasks"], "4.3 7.9 11.9": ["sedimentary"], "7.9 10.5 3.3": ["chanced"], "5.2 10.7 10.0": ["shutterbugs"], "4.1 14.8 25.0": ["peninsular"], "5.6 13.4 -2.0": ["ransack"], "2.5 2.5 20.1": ["polyp"], "-4.3 6.6 8.3": ["antiabortion"], "10.7 4.3 15.1": ["guv"], "9.4 10.4 9.8": ["proverbs"], "19.1 7.4 25.7": ["toothed"], "-10.7 35.5 6.7": ["fratricide"], "5.3 12.3 9.9": ["blustering"], "-1.5 17.3 -1.6": ["substate"], "8.3 -0.4 13.9": ["yon"], "7.2 3.4 15.4": ["nudists"], "-0.8 -0.4 12.0": ["translocation"], "-1.1 11.7 9.5": ["blackballed"], "2.3 4.0 29.8": ["tamale"], "4.5 11.0 10.7": ["pomposity"], "-5.8 12.1 2.2": ["evasions"], "-7.0 7.8 20.5": ["zinfandel"], "-8.5 0.9 3.4": ["raloxifene"], "6.2 9.3 10.8": ["garbed"], "5.6 0.3 9.6": ["tramway"], "-2.7 1.5 -0.5": ["rehabilitates"], "17.7 27.1 7.4": ["exploiters"], "1.5 9.7 26.3": ["cheesesteak"], "2.5 4.5 19.0": ["brooches"], "4.4 7.9 4.1": ["untended"], "-1.0 -1.0 0.8": ["relook"], "15.6 16.7 5.9": ["deform"], "7.4 18.6 9.6": ["smallness"], "9.3 -0.4 1.9": ["scrapheap"], "15.4 13.3 11.4": ["mongering"], "31.5 10.9 10.3": ["monstrosities"], "1.9 3.0 11.4": ["spacewalking"], "7.7 2.8 -5.1": ["biosensors"], "5.6 1.9 -2.1": ["disproving"], "2.9 9.1 1.2": ["reentered"], "12.2 24.1 8.1": ["extortionist"], "-0.9 3.5 16.1": ["trackwork"], "11.2 7.7 9.9": ["oughta"], "8.5 15.4 2.7": ["fallibility"], "-1.1 4.0 0.7": ["sportspeople"], "10.6 15.3 7.6": ["ashen"], "-7.5 14.2 5.0": ["deprivations"], "4.6 11.2 8.8": ["biomolecules"], "-4.4 8.0 5.2": ["mikes"], "8.9 8.0 -1.4": ["wristwatches"], "-8.3 -0.9 3.5": ["babysat"], "9.2 10.0 3.8": ["earl"], "6.4 15.6 6.0": ["browbeat"], "1.0 5.0 11.3": ["francophones"], "7.1 18.3 3.9": ["servile"], "11.4 13.3 7.5": ["fells"], "13.7 3.1 14.7": ["bodysuit"], "3.2 22.2 9.7": ["negro"], "-7.8 4.7 5.2": ["khadi"], "4.3 18.2 9.0": ["modifiers"], "11.4 4.3 10.1": ["pooped"], "-2.3 -0.0 10.5": ["decile"], "3.9 4.0 5.3": ["ipad"], "16.3 -0.0 10.6": ["nu"], "-12.2 6.4 18.2": ["riesling"], "-4.8 -1.5 11.7": ["duathlon"], "5.4 19.5 8.9": ["unintelligent"], "-5.2 5.6 21.6": ["steakhouses"], "13.7 14.0 13.0": ["idyll"], "5.4 8.7 13.0": ["jowl"], "9.5 4.2 -1.7": ["rarified"], "1.8 3.4 12.2": ["swabbing"], "7.0 7.8 7.2": ["ere"], "-4.7 5.0 3.7": ["downhearted"], "17.4 7.3 14.4": ["ruddy"], "-3.5 21.7 6.4": ["snitches"], "-3.8 9.9 6.3": ["tased"], "1.7 9.2 5.8": ["corded"], "13.2 -0.9 10.4": ["midsession"], "-2.8 5.6 3.8": ["uncollectible", "sagt"], "0.9 2.4 13.5": ["lutein"], "5.9 14.4 9.7": ["shortsightedness"], "12.0 2.7 18.8": ["chucks"], "4.6 9.2 9.6": ["hitchhikers"], "10.6 11.8 15.5": ["pyro"], "15.9 13.6 13.5": ["thudding"], "4.9 8.2 13.6": ["consonants"], "13.6 10.8 8.0": ["windblown"], "-2.3 3.2 2.3": ["lossless"], "-0.8 1.0 12.2": ["honeymoons"], "0.2 11.4 4.2": ["overloads"], "3.4 0.5 6.6": ["wah"], "7.8 9.4 12.9": ["pergola"], "11.7 10.4 16.3": ["choker"], "7.5 4.2 6.5": ["tachometer"], "6.8 -2.8 5.3": ["ahs"], "-0.8 -1.2 11.6": ["drawstring"], "9.4 9.4 15.7": ["buzzers"], "6.2 20.3 10.9": ["softie"], "4.7 -2.2 14.7": ["han"], "13.5 0.3 0.1": ["tooting"], "3.9 13.8 2.3": ["misuses"], "-5.3 6.9 10.0": ["reburial"], "-7.1 16.8 12.7": ["interjects"], "5.0 5.3 -0.3": ["mislaid"], "-1.1 4.7 12.7": ["goofiness"], "5.6 13.8 9.0": ["whiffing"], "9.1 7.7 30.2": ["tuber"], "7.6 8.1 7.4": ["boggy"], "4.8 15.1 15.3": ["biofilms"], "11.4 12.1 4.9": ["commonest"], "8.0 15.6 7.5": ["kindred"], "2.0 7.9 3.5": ["prescience"], "27.2 7.3 8.0": ["whizzes"], "4.0 12.5 1.6": ["engrained"], "7.4 -4.6 -6.0": ["allaying"], "16.1 16.2 11.1": ["louts"], "-12.0 7.7 25.4": ["forages"], "5.5 -7.8 8.0": ["scrimping"], "29.4 14.0 15.4": ["maw"], "-4.0 0.7 1.3": ["arthroscopy"], "12.7 11.6 13.0": ["ripper"], "3.7 11.9 3.8": ["assertively"], "1.8 12.2 6.1": ["segmenting"], "-4.4 4.3 5.0": ["redraft"], "17.7 7.3 8.0": ["forlornly"], "3.5 2.8 10.8": ["quant"], "6.3 6.9 6.3": ["maneuverings"], "-8.0 3.6 2.4": ["lockdowns"], "1.5 14.2 12.4": ["longings"], "6.7 9.1 15.8": ["mortician"], "-0.4 -1.6 2.5": ["efavirenz"], "1.9 11.5 2.7": ["reunified"], "-0.0 0.2 -0.7": ["transdermal"], "7.6 5.0 10.0": ["blessedly"], "-0.4 -2.8 1.0": ["renegotiations"], "-7.2 10.1 -1.4": ["censuring"], "7.0 11.6 4.5": ["jetlag"], "13.1 9.9 18.2": ["mucky"], "0.6 7.8 11.0": ["breakpoint"], "6.6 15.0 5.6": ["slavish"], "5.4 6.1 3.8": ["hamming"], "10.6 5.3 11.2": ["butlers"], "1.0 7.9 -4.3": ["decentralizing"], "-4.9 10.5 17.3": ["cultivar"], "2.4 9.6 9.9": ["homebody"], "4.2 12.8 16.8": ["yakuza"], "1.7 8.6 1.3": ["superconductors"], "7.8 15.5 8.5": ["wanderer"], "3.1 -1.6 0.8": ["birr"], "5.7 12.0 3.3": ["exhibitionist"], "-2.7 9.5 -2.9": ["directorates"], "6.6 5.8 9.7": ["blacksmithing"], "4.1 10.9 9.0": ["stoops"], "2.5 13.0 10.3": ["consonant"], "4.6 4.8 23.1": ["shortbread"], "-0.6 3.5 5.8": ["timesheet"], "-0.2 -2.3 -0.7": ["empaneled"], "2.4 15.3 7.3": ["cordially"], "4.8 4.6 7.9": ["ut"], "1.7 14.0 9.6": ["bisexuals"], "-4.0 0.2 6.1": ["estradiol"], "5.8 11.1 7.1": ["thrillingly"], "2.2 6.9 6.1": ["expressiveness"], "-10.3 5.5 1.8": ["empathized"], "12.0 3.8 13.8": ["talentless"], "-0.9 8.6 3.3": ["heartaches"], "-2.4 -0.2 -0.0": ["musicologist"], "5.8 23.9 7.1": ["howitzers"], "-0.2 11.0 1.3": ["occassion"], "1.3 16.7 9.2": ["conformist"], "2.5 2.2 6.0": ["spinouts"], "6.0 7.6 2.0": ["quasars"], "4.8 14.5 10.6": ["constancy"], "1.4 4.1 20.8": ["acidification"], "-10.2 3.6 17.4": ["kharif"], "1.3 19.5 -1.6": ["interferences"], "2.5 25.1 1.2": ["interventionism"], "0.3 1.0 7.6": ["germinated"], "-2.3 10.9 9.9": ["wetness"], "10.1 6.4 33.7": ["flounders"], "5.8 13.8 10.5": ["hydrophobic"], "12.0 22.0 13.2": ["jackals"], "-0.1 -4.1 19.6": ["zircon"], "12.1 9.9 10.0": ["swatches"], "13.4 7.4 0.5": ["repairmen"], "9.5 4.6 3.8": ["skywalk"], "16.2 21.5 9.5": ["watchtowers"], "18.2 15.5 7.8": ["pierces"], "6.2 8.4 3.5": ["undemanding"], "10.6 4.5 7.8": ["esplanade"], "1.8 2.6 10.7": ["hacienda"], "0.4 13.4 6.0": ["debasement"], "18.8 -1.5 15.2": ["snacked"], "1.9 4.3 17.2": ["underdone"], "16.7 9.8 9.5": ["thunk"], "-1.7 7.4 11.9": ["cellos"], "9.8 13.5 12.3": ["blights"], "-4.0 13.7 6.3": ["unbuckled"], "1.5 -5.3 8.5": ["racier"], "11.5 6.8 20.6": ["hutch"], "27.5 11.4 29.7": ["toothy"], "13.0 11.9 8.0": ["disgorge"], "24.0 16.6 20.3": ["sprite"], "3.0 8.2 7.0": ["counteracted"], "-2.1 10.3 1.9": ["juxtapose"], "9.9 -5.1 1.8": ["ver"], "1.9 3.6 1.2": ["badging"], "8.5 13.1 7.1": ["perversity"], "12.1 15.0 2.5": ["sniffer"], "8.8 17.2 13.9": ["douchebag"], "6.9 5.4 13.6": ["ahh"], "-4.3 6.1 5.7": ["thalassemia", "bevirimat"], "8.1 1.8 10.5": ["loco"], "-1.8 5.2 4.2": ["niobium"], "2.1 7.5 -0.2": ["amalgamating"], "-9.0 33.8 5.9": ["warfighting"], "12.8 10.3 10.1": ["careen"], "8.3 16.2 3.8": ["walling"], "6.4 9.2 4.8": ["snickered"], "9.6 12.3 4.9": ["shames"], "4.1 12.7 6.1": ["homoerotic"], "-5.0 6.9 12.5": ["fibroblasts"], "-3.2 7.8 -2.1": ["realizable"], "4.6 11.4 9.8": ["junkyards"], "17.4 8.5 14.0": ["heaves"], "-1.3 5.3 0.3": ["uncorrected"], "1.8 5.9 -1.6": ["atoning"], "-0.0 -2.8 9.0": ["yogurts"], "0.3 29.9 4.0": ["peshmerga"], "11.4 9.4 6.4": ["gantlet"], "5.3 3.9 2.3": ["lubricating"], "10.1 3.2 3.7": ["homeware"], "2.0 3.4 16.0": ["tic"], "4.2 0.6 26.5": ["empanadas"], "-3.7 9.0 -2.8": ["cleanses"], "-1.1 0.3 10.3": ["upticks"], "2.9 -4.0 11.0": ["simulcasts"], "6.3 -2.3 11.2": ["merengue"], "18.7 13.6 12.6": ["humping"], "0.3 21.3 9.6": ["statecraft"], "4.9 -1.4 7.8": ["giftware"], "0.8 4.2 1.8": ["editorially"], "9.2 3.6 12.2": ["needlepoint"], "-4.4 9.6 0.0": ["defendable", "propounds"], "2.9 2.7 14.9": ["brasserie"], "-6.9 15.0 6.3": ["honorific"], "5.7 8.0 3.0": ["superconductor"], "-4.7 14.5 7.1": ["wisecrack"], "7.5 9.8 4.9": ["flatlands"], "-6.6 8.2 6.2": ["excision"], "2.1 9.0 12.7": ["unspoilt"], "11.4 3.2 4.2": ["merchandiser"], "-0.7 10.4 13.1": ["towboat"], "0.6 8.9 0.0": ["amortizing"], "10.4 10.1 15.5": ["yuck"], "2.8 14.7 5.0": ["skirmishing"], "-0.5 9.0 11.7": ["showboat"], "8.0 10.8 11.7": ["slovenly"], "6.7 4.7 9.7": ["prepubescent"], "6.3 1.1 0.6": ["outshined"], "10.7 -2.0 12.6": ["tummies"], "11.2 4.3 3.9": ["jacuzzi"], "12.1 8.9 3.9": ["bullfighter"], "7.5 12.4 17.1": ["aurora"], "-4.4 12.5 14.7": ["kata"], "1.8 2.6 0.8": ["lawfulness"], "5.7 17.7 3.3": ["insularity"], "8.2 1.6 -2.0": ["activites"], "3.1 5.8 18.2": ["propecia"], "0.2 12.8 0.2": ["fungible"], "-2.3 0.6 6.8": ["onboarding"], "4.6 8.0 -0.8": ["cheapens"], "6.4 12.3 10.2": ["prognosticator"], "8.4 9.5 5.0": ["billionths"], "3.2 2.9 31.4": ["bayside"], "3.6 9.9 7.1": ["backrow"], "5.8 10.8 4.1": ["oldie"], "5.2 8.0 8.6": ["intermingle"], "7.8 9.7 9.8": ["cajas"], "4.9 3.9 19.5": ["kung"], "9.5 6.7 13.7": ["fanciers"], "4.8 1.2 2.1": ["reposed"], "7.9 13.5 13.9": ["entomologists"], "4.9 6.1 62.2": ["pollock"], "3.2 20.8 2.8": ["axiomatic"], "13.3 3.1 -3.4": ["inhouse"], "2.0 4.1 11.1": ["casted"], "7.3 6.2 -1.0": ["studiously"], "-4.8 11.9 2.3": ["repairable"], "4.1 -5.0 -1.0": ["ments"], "2.2 4.0 16.6": ["rosettes"], "1.3 1.0 14.9": ["uppers"], "14.9 6.3 2.7": ["boombox"], "14.3 10.0 10.7": ["barmy"], "6.9 10.2 5.7": ["unrecoverable"], "-8.5 0.4 7.7": ["toluene"], "7.2 -2.8 5.7": ["kee"], "3.9 10.4 33.1": ["fisherfolk"], "6.4 18.0 3.8": ["demagogic"], "0.9 2.7 6.4": ["preapproved"], "-4.8 17.1 3.4": ["mottos"], "5.6 12.1 10.3": ["neurotoxin"], "6.2 6.6 5.8": ["barrios"], "-7.7 2.4 3.6": ["understudies"], "4.1 3.6 7.9": ["commish"], "5.4 6.9 5.6": ["fitfully"], "16.9 28.6 8.1": ["flamethrower"], "1.4 -9.0 -0.1": ["overslept"], "2.4 6.2 -5.6": ["romanced"], "7.0 9.7 9.1": ["grandiosity"], "21.7 6.9 5.7": ["cacophonous"], "-4.5 7.0 9.2": ["sketchbook"], "10.4 5.2 21.5": ["sideboard"], "3.5 20.3 6.6": ["detonations"], "2.7 18.4 6.3": ["mutinous"], "-4.2 11.0 5.0": ["landholdings"], "6.6 3.4 13.9": ["festivalgoers"], "-2.5 6.3 5.6": ["cornet"], "-6.2 10.9 5.3": ["crosstalk"], "-7.0 6.4 5.2": ["digression"], "1.1 7.3 6.1": ["unclothed"], "28.1 -0.3 0.4": ["fiascos"], "-0.4 10.7 13.2": ["gangsterism"], "6.8 4.6 13.7": ["rosette"], "-1.0 15.9 5.9": ["ineffable"], "15.0 20.0 2.6": ["thunders"], "4.0 -1.3 9.9": ["restorers"], "2.1 6.4 17.2": ["brewpub"], "8.0 10.7 4.2": ["minutely"], "0.1 -3.3 10.3": ["mos"], "-3.6 1.6 1.3": ["microbicides"], "10.5 10.3 11.7": ["redder"], "11.2 17.4 4.6": ["sissies"], "-5.2 3.0 6.0": ["showrunner"], "11.8 6.0 -5.1": ["scrubland"], "-1.0 20.3 11.1": ["paganism"], "-0.8 9.5 4.1": ["romanticize"], "-5.5 13.0 1.7": ["constitutionalism"], "9.0 8.1 3.9": ["dubiously"], "-1.1 13.3 -3.0": ["determinative"], "-2.1 -0.1 9.3": ["nonmember"], "-1.6 7.1 1.8": ["softphone"], "7.8 12.0 10.4": ["cannibalized"], "5.4 7.2 17.0": ["drifters"], "8.2 14.1 15.8": ["teasingly"], "6.7 4.0 13.0": ["wackiness"], "12.8 14.4 9.2": ["hailstones"], "3.9 -3.6 10.6": ["ia"], "6.1 4.0 8.2": ["quickbooks"], "-2.4 17.6 12.5": ["pronoun"], "3.4 14.3 5.6": ["irritations"], "3.6 -5.0 12.7": ["cha"], "-3.2 11.9 7.6": ["retweet"], "6.2 19.7 4.7": ["bugbear"], "4.9 13.8 10.3": ["verifiably"], "4.0 8.8 13.2": ["coops"], "-5.8 10.5 12.2": ["peramivir"], "9.9 17.9 1.6": ["apparatuses"], "0.1 14.8 28.3": ["fowls"], "5.2 11.0 18.3": ["picnickers"], "-2.4 7.4 9.8": ["semiautomatic"], "17.9 1.2 12.3": ["yearslong"], "5.2 -0.2 7.1": ["sonorous"], "-10.3 14.5 0.4": ["exculpatory"], "-2.0 0.7 7.3": ["hardcopy"], "9.5 14.1 25.3": ["dockyard"], "-4.5 0.9 11.4": ["downspouts"], "1.3 6.8 3.0": ["wkts"], "-5.0 11.2 4.3": ["suppositions"], "7.9 14.7 9.5": ["awfulness"], "1.0 7.2 8.1": ["skarn"], "7.8 8.9 8.0": ["overexcited"], "9.6 12.8 -2.3": ["wishers"], "5.4 20.5 1.2": ["defile"], "7.6 2.2 0.7": ["entrepreneurialism"], "-7.2 -0.7 -3.2": ["stenosis"], "-2.0 24.1 5.0": ["servicewomen"], "9.1 -3.2 12.4": ["climaxing"], "2.0 12.8 7.7": ["misjudge"], "-0.2 8.0 2.3": ["superseding"], "-0.5 4.0 11.9": ["antic"], "-3.0 7.4 9.0": ["hardtop"], "5.0 21.0 7.2": ["prophesy"], "15.0 11.1 6.4": ["greenwashing"], "4.4 3.8 8.2": ["grayscale"], "-10.3 22.3 17.6": ["medevac"], "0.4 19.5 1.3": ["metastasize"], "2.3 4.8 1.6": ["titillate"], "-0.9 8.6 7.6": ["nonsmoker"], "2.6 7.6 11.9": ["stutters"], "9.1 3.2 2.0": ["physiologist"], "2.7 7.6 15.0": ["subsoil"], "10.9 2.2 0.3": ["cozier"], "7.7 11.8 -1.8": ["illiterates"], "5.9 10.8 2.2": ["rocketry"], "-5.1 24.4 9.6": ["corpsman"], "21.1 23.3 26.4": ["hornets"], "8.2 5.2 15.3": ["corked"], "6.6 3.9 8.7": ["augured"], "10.2 9.4 11.5": ["overeager"], "-10.7 7.6 1.4": ["emphases"], "-2.5 9.9 10.5": ["moorland"], "9.0 7.6 15.5": ["pucker"], "1.0 10.6 4.8": ["messiness"], "4.4 6.0 3.8": ["intermediation"], "9.9 9.0 8.9": ["flitted"], "5.4 9.1 6.6": ["countrywoman"], "0.5 11.3 13.0": ["tipper"], "1.3 6.7 24.5": ["nectarines"], "2.3 4.6 10.8": ["stratum"], "0.7 16.7 11.6": ["sharpshooting"], "6.0 4.0 9.6": ["bongos"], "-2.8 7.8 -2.5": ["contraventions"], "1.4 -3.4 10.2": ["braiding"], "17.0 7.8 7.4": ["quadrangle"], "2.4 6.4 -2.9": ["cps"], "-4.6 6.0 18.6": ["lifejacket"], "6.6 -6.1 21.6": ["fishnets"], "-2.5 10.3 26.3": ["waterfronts"], "4.6 17.7 4.8": ["penetrations"], "18.6 6.9 8.1": ["stanchion"], "1.1 7.8 1.4": ["compactness"], "-5.4 1.6 -0.8": ["statutorily"], "4.1 11.7 8.3": ["egotism"], "5.2 8.3 18.8": ["clipper"], "5.9 1.5 10.7": ["dj"], "-3.6 2.2 6.1": ["assemblywoman"], "5.4 5.3 9.2": ["paupers"], "12.9 0.2 11.2": ["ina"], "10.0 8.1 8.5": ["reassembling"], "17.3 7.7 14.6": ["sooty"], "4.7 17.9 22.6": ["dieter"], "-1.2 8.2 0.9": ["heartrending"], "-5.5 12.3 2.7": ["analytically"], "10.7 11.5 7.3": ["gulps"], "9.9 6.8 6.8": ["rudiments"], "0.8 17.8 8.2": ["subverts"], "34.5 1.3 10.8": ["supersize"], "1.8 8.8 20.1": ["mead"], "8.0 9.0 8.5": ["tryptophan"], "-0.2 8.9 -0.3": ["possesion"], "2.8 -3.8 5.3": ["lr"], "-0.0 18.6 7.3": ["emote"], "2.2 8.2 6.0": ["overbroad"], "-7.9 1.9 2.1": ["austriamicrosystems"], "7.3 3.7 10.2": ["tabernacle"], "19.1 15.5 14.6": ["hulks"], "14.1 1.8 3.7": ["tuesday"], "5.9 2.8 0.3": ["reformat"], "-1.7 13.7 7.7": ["epidermis"], "2.4 9.1 9.6": ["ands"], "0.0 1.1 2.6": ["urological"], "10.9 2.6 11.3": ["argon"], "17.4 14.9 8.5": ["iniquity"], "14.0 26.1 22.2": ["gnats"], "23.0 10.5 2.7": ["zillions"], "5.3 4.1 5.3": ["wombs"], "-4.5 11.5 -1.0": ["propounded"], "3.3 13.6 2.6": ["antecedent"], "11.1 8.5 2.9": ["trashes"], "10.8 13.0 9.9": ["foosball"], "7.9 0.0 0.5": ["garlanded"], "11.0 1.7 5.2": ["dee"], "6.5 12.8 -0.3": ["editable"], "7.0 25.1 7.9": ["collectivism"], "5.7 4.1 3.4": ["pls"], "-7.8 3.0 8.5": ["librettist"], "-9.7 6.2 5.5": ["astringent"], "10.8 8.3 6.3": ["pilfer"], "22.9 3.6 30.1": ["gummy"], "-2.5 24.2 6.1": ["mentalities"], "3.4 1.6 2.4": ["weightier"], "-0.3 -1.2 2.1": ["carr"], "5.0 9.8 -5.4": ["internationalized"], "-0.3 -6.5 -6.8": ["syndicating"], "-0.7 6.7 1.3": ["append"], "7.2 2.8 11.0": ["regionwide"], "11.0 3.3 7.4": ["armful"], "11.9 9.5 5.2": ["unluckiest"], "-5.0 24.2 8.1": ["naxal"], "10.2 18.0 8.2": ["whosoever"], "3.1 5.7 3.9": ["honeymooning"], "5.7 4.8 13.0": ["canoeist"], "-4.1 14.8 2.4": ["empathic"], "1.3 18.4 6.6": ["externalities"], "1.8 5.7 3.2": ["ruminating"], "13.0 5.5 14.2": ["floatation"], "10.1 9.3 13.2": ["billiard"], "11.6 15.2 5.3": ["preprogrammed"], "-0.1 3.3 9.9": ["gating"], "0.1 16.3 14.3": ["fornication"], "17.0 0.4 16.5": ["olympics"], "29.0 11.9 7.5": ["blimps"], "5.8 -3.1 4.3": ["leotards"], "-0.6 10.5 20.7": ["seascapes"], "9.7 12.7 11.2": ["foxy"], "12.3 16.5 14.1": ["unearthly"], "18.8 -0.3 8.0": ["cherubic"], "8.8 15.3 13.4": ["orbiters"], "9.9 0.5 18.8": ["sequin"], "1.2 19.8 -0.2": ["mystics"], "23.2 9.7 15.0": ["sombrero"], "16.2 5.6 9.7": ["byzantine"], "6.0 27.4 9.9": ["exterminating"], "-0.9 1.2 -2.1": ["showerheads"], "2.5 -1.1 0.2": ["bumpier"], "-1.8 9.2 -0.1": ["conflate"], "-2.2 -0.7 17.9": ["housemaids"], "8.6 8.1 13.4": ["prizing"], "5.9 -0.8 6.6": ["hee"], "-3.9 13.2 0.6": ["miscommunications"], "22.5 15.4 24.3": ["ladybug"], "-5.4 5.7 -4.5": ["inculcating"], "6.8 15.8 11.6": ["inexact"], "-6.3 37.9 0.1": ["counterterrorist"], "1.3 27.4 7.1": ["unpardonable"], "8.5 9.9 4.7": ["geometrical"], "14.6 2.9 10.6": ["staves"], "5.7 7.2 7.9": ["underaged"], "3.5 4.9 5.3": ["vacillated"], "15.7 5.6 11.2": ["tiptoes"], "15.3 6.8 7.8": ["fakery"], "-2.4 5.1 7.8": ["ivories"], "-1.7 -3.2 -4.4": ["eds"], "9.2 4.2 3.5": ["dustbins"], "4.1 1.5 0.1": ["signposted"], "4.8 10.8 12.8": ["faceplate"], "3.6 18.2 32.1": ["dogwood"], "3.9 6.6 2.5": ["nitroglycerin"], "6.1 28.4 3.2": ["outflank"], "6.3 5.8 7.3": ["dexterous"], "3.5 -2.1 7.3": ["matrons"], "0.2 10.3 10.7": ["lodger"], "-0.1 7.5 32.5": ["parsnips"], "-1.0 9.6 5.2": ["sisterly"], "-4.1 18.4 6.3": ["republicanism"], "1.8 6.4 8.1": ["ipilimumab"], "-4.5 -0.6 7.3": ["multiservice"], "13.5 3.9 10.4": ["bauble"], "-5.9 -1.0 13.3": ["germanium"], "7.2 18.4 6.6": ["jingoism"], "17.7 12.7 13.8": ["freeloaders"], "6.1 0.8 5.8": ["biorefinery"], "12.9 11.1 13.4": ["goodly"], "-10.9 4.4 2.4": ["redaction"], "5.9 -0.9 8.8": ["lah"], "-10.9 3.9 11.5": ["remodelers"], "8.4 10.4 2.1": ["drumbeats"], "11.5 5.4 11.6": ["supertankers"], "2.8 -0.9 14.9": ["joinery"], "14.3 6.9 5.4": ["isn"], "-0.0 14.2 12.7": ["permalink"], "-1.7 10.8 9.8": ["baseboards"], "-7.8 7.1 5.7": ["overwritten"], "-1.1 -3.5 10.1": ["hemline"], "12.5 4.3 3.8": ["leaseholder"], "9.4 34.2 3.1": ["foxholes"], "6.3 1.3 4.1": ["eek"], "5.5 -1.2 11.5": ["nags"], "16.3 -5.6 -8.9": ["relaunches"], "14.2 5.3 5.8": ["loftiest"], "12.2 33.1 14.8": ["pestilence"], "-2.8 0.8 15.0": ["snus"], "1.2 3.0 12.3": ["autorickshaws"], "0.4 5.6 2.1": ["debits"], "2.2 8.0 31.5": ["harbormaster"], "-0.6 20.2 2.0": ["revisionism"], "-5.5 18.1 13.0": ["electorally"], "-4.0 16.7 -1.8": ["incorruptible"], "6.9 2.9 12.9": ["wallowed"], "-14.8 1.6 7.4": ["internists"], "-7.6 7.9 12.4": ["sommeliers"], "7.1 14.0 2.6": ["bookworm"], "6.2 10.7 1.2": ["unconvincingly"], "-1.7 13.6 5.6": ["cheerfulness"], "7.3 1.4 13.9": ["frill"], "8.9 15.8 4.4": ["foursquare"], "-3.4 5.6 5.5": ["oud"], "1.3 13.6 4.6": ["humbles"], "-0.2 6.1 9.5": ["regionalized"], "-2.4 2.4 12.8": ["agritourism"], "5.0 7.5 17.4": ["leanest"], "-2.3 10.2 10.1": ["codifying"], "19.4 24.4 12.6": ["sprites"], "13.3 15.3 27.1": ["gaff"], "3.6 -0.5 4.4": ["sheepskin"], "7.5 5.3 6.3": ["fireside"], "6.2 6.5 19.1": ["teatime"], "-1.0 4.3 -0.5": ["cedi"], "6.7 9.1 -0.2": ["revaluing"], "8.4 16.0 23.6": ["cedars"], "0.4 19.7 7.7": ["acquiescing"], "9.7 27.6 13.4": ["animalistic"], "10.8 4.5 8.2": ["crotchety"], "1.6 4.0 9.3": ["recapitalizations"], "-9.2 2.5 24.1": ["copra"], "-0.8 5.0 11.0": ["nonperforming"], "-1.4 6.7 1.9": ["telecommuters"], "5.9 14.8 9.0": ["glibly"], "7.7 17.2 15.4": ["asexual"], "-0.9 9.0 6.9": ["dialogs"], "10.5 2.5 4.3": ["andthe"], "9.9 -0.3 9.4": ["pares"], "5.1 -5.5 4.4": ["monogram"], "3.7 4.4 9.3": ["finessed"], "-1.3 -3.1 7.2": ["surfactants"], "8.3 7.3 3.6": ["punked"], "-2.1 11.1 8.0": ["linebacking"], "10.1 19.2 11.5": ["clammy"], "-2.5 1.0 4.6": ["schmaltzy"], "-7.3 17.1 -2.8": ["radicalize"], "2.9 2.0 18.0": ["femme"], "4.9 13.0 8.9": ["unreality"], "-1.2 10.2 5.4": ["believably"], "3.1 -3.4 1.7": ["talc"], "12.0 7.0 6.8": ["stilled"], "22.4 0.7 6.8": ["drooped"], "-1.8 11.3 16.3": ["shanks"], "6.9 8.3 20.6": ["krewe"], "-2.7 -3.5 8.1": ["olanzapine"], "17.1 -0.7 8.0": ["gawked"], "-4.3 12.9 5.9": ["interdicted"], "9.7 17.4 7.5": ["simpleton"], "9.7 5.4 11.2": ["craning"], "4.7 7.0 2.1": ["chickened"], "5.0 6.9 4.7": ["yaw"], "8.4 5.1 16.0": ["toenail"], "7.0 18.4 10.8": ["globalism"], "6.0 15.8 12.0": ["buildups"], "11.7 14.9 6.8": ["impermeable"], "18.0 6.6 9.4": ["bigtime"], "16.1 0.1 3.5": ["trebling"], "-8.3 5.9 5.2": ["overages"], "-2.0 7.8 18.0": ["bitters"], "6.9 13.7 2.4": ["habituated"], "16.0 7.9 5.5": ["severs"], "5.1 3.9 7.6": ["straightens"], "1.7 7.6 1.7": ["numerology"], "12.8 0.7 -4.4": ["beeped"], "8.0 12.7 19.2": ["groundhogs"], "-1.6 4.4 48.0": ["albacore"], "-2.7 36.0 -1.0": ["suppressive"], "11.8 5.6 15.0": ["onyx"], "8.4 7.3 6.2": ["headbutting"], "1.6 -1.5 7.8": ["alli"], "6.9 15.9 7.4": ["misjudging"], "4.3 7.7 11.9": ["blacksmiths"], "17.0 12.1 5.7": ["marketeers"], "7.9 -0.2 23.0": ["tusk"], "16.7 4.8 10.9": ["pinwheels"], "8.5 9.5 -1.9": ["keenest"], "10.7 5.0 22.0": ["kun"], "7.6 12.0 4.3": ["reveres"], "4.1 12.5 14.3": ["scabies"], "14.7 7.4 16.3": ["scrabble"], "2.0 19.0 1.4": ["infringers"], "13.1 19.0 11.6": ["crevasses"], "9.4 11.3 4.8": ["screeches"], "15.6 10.3 15.3": ["frisbee"], "-8.9 1.7 6.2": ["caesarean"], "-0.2 11.6 26.9": ["islander"], "7.1 7.9 4.1": ["preselected"], "-1.1 11.3 18.8": ["bluetongue"], "7.2 -4.0 18.2": ["mai"], "14.8 8.8 6.2": ["fantasyland"], "7.0 9.8 12.2": ["snookered"], "-4.6 4.2 15.1": ["histology"], "11.8 17.5 37.0": ["cicada"], "15.6 21.8 7.9": ["awakes"], "7.3 10.8 16.4": ["cheapskate"], "3.0 7.1 11.4": ["coaxes"], "5.2 4.5 7.6": ["polyglot"], "17.2 7.2 -1.1": ["phonograph"], "-7.2 7.4 4.3": ["repost"], "4.4 10.4 11.3": ["mortuaries"], "17.5 -5.1 10.4": ["bulged"], "0.7 4.6 12.4": ["pooja"], "1.6 -3.7 11.5": ["sidebars"], "10.0 5.3 5.5": ["copybook"], "-5.9 0.2 6.6": ["pawning"], "1.5 -2.1 7.9": ["paycheques"], "12.2 3.3 9.4": ["frieze"], "13.3 21.5 11.1": ["hellacious"], "10.8 18.0 11.9": ["devilishly"], "7.7 20.0 5.7": ["mythos"], "19.4 3.4 5.2": ["outbidding"], "16.7 6.8 19.7": ["topiary"], "15.4 11.6 10.0": ["crumple"], "-0.3 16.9 7.9": ["compartmentalize"], "9.2 8.7 11.4": ["barbeques"], "15.1 -6.5 3.6": ["semiretired"], "6.8 0.7 7.5": ["mit"], "11.7 -2.2 1.8": ["rescinds"], "12.7 18.5 4.7": ["watchtower"], "10.5 -5.1 5.2": ["stapling"], "4.3 5.6 11.0": ["rambles"], "8.4 1.3 21.7": ["chalky"], "10.5 5.4 21.0": ["canapes"], "5.8 20.6 11.5": ["gringo"], "11.2 11.8 8.1": ["steampunk"], "-1.7 1.6 11.0": ["atorvastatin"], "-7.1 11.4 22.7": ["daylilies"], "24.9 26.3 4.1": ["nasties"], "19.3 2.4 -3.6": ["forayed"], "1.9 6.5 22.0": ["anise"], "-2.6 8.1 13.1": ["hems"], "-3.2 3.8 2.5": ["distills"], "13.9 13.7 14.7": ["hollowing"], "8.9 28.7 13.7": ["deathly"], "3.9 16.5 9.5": ["exterminators"], "7.3 4.8 16.4": ["hooey"], "7.1 7.8 0.5": ["ionic"], "19.3 15.2 8.9": ["grabber"], "-2.7 13.0 6.3": ["modernists"], "-2.2 5.3 20.2": ["seatings"], "4.7 11.1 -2.5": ["infallibility"], "4.0 2.6 34.1": ["miso"], "5.0 6.8 18.5": ["parasailing"], "-3.9 0.2 12.8": ["copay"], "-1.2 7.2 2.1": ["valuer"], "7.3 -1.1 5.4": ["vibrators"], "6.8 0.3 -0.7": ["scrawling"], "23.1 18.2 9.5": ["glowering"], "6.1 7.4 20.3": ["headland"], "2.3 18.2 -0.6": ["inarguably"], "5.2 18.7 16.2": ["spore"], "6.4 13.1 -1.7": ["excoriating"], "1.2 6.5 11.0": ["foxtrot"], "-1.2 6.0 12.7": ["headmasters"], "2.1 11.0 9.2": ["capo"], "19.8 5.6 17.7": ["derrick"], "6.9 8.8 6.9": ["leftward"], "4.2 14.6 47.6": ["lionfish"], "21.4 14.9 18.6": ["greedily"], "-7.4 10.8 15.4": ["prorogation"], "2.5 3.7 8.8": ["hyperlocal"], "5.8 6.5 11.7": ["wintery"], "6.8 21.9 10.7": ["illusive"], "23.0 12.6 13.5": ["denizen"], "8.2 3.2 9.3": ["stirrups"], "-3.0 7.4 7.3": ["rumination"], "9.6 3.6 10.2": ["stepladder"], "15.9 23.3 16.8": ["bloodsuckers"], "9.5 6.6 12.1": ["smokey"], "0.5 8.0 12.0": ["england"], "11.2 -3.4 11.4": ["bongs"], "2.8 2.2 11.9": ["fam"], "-4.2 2.3 24.9": ["burley"], "3.1 6.6 25.7": ["stoneware"], "-11.3 6.4 3.5": ["reassignments"], "7.6 11.1 8.8": ["syncopated"], "-0.4 8.5 11.7": ["flinty"], "-2.5 10.1 6.3": ["disenfranchising"], "10.6 19.1 12.8": ["heedless"], "-6.9 3.7 11.4": ["hypothermic"], "-3.3 -6.4 15.2": ["cornrows"], "4.8 11.4 12.8": ["impoverish"], "5.5 14.6 16.7": ["brushstrokes"], "-4.5 17.0 7.2": ["overthrows"], "5.5 16.1 8.6": ["proletarian"], "11.6 -6.8 0.6": ["brimmed"], "0.6 2.3 3.2": ["profiler"], "7.5 7.8 3.9": ["cloudburst"], "-3.4 8.8 8.7": ["chieftaincy"], "17.4 6.7 10.6": ["bizarro"], "18.9 12.4 23.1": ["tarantulas"], "-2.3 4.3 22.7": ["matzo"], "5.5 16.9 17.9": ["buckshot"], "18.4 7.4 6.0": ["matchbox"], "14.3 1.0 3.3": ["prams"], "11.2 11.8 17.1": ["arrowhead"], "0.9 5.7 9.0": ["futher"], "5.0 14.0 7.4": ["cowl"], "12.0 2.2 18.1": ["butterscotch"], "2.3 9.1 7.3": ["nullifies"], "8.9 4.5 7.2": ["shagging"], "3.4 3.4 0.5": ["billers"], "15.7 11.3 1.7": ["namesakes"], "9.2 7.5 14.2": ["pugs"], "0.1 9.0 13.7": ["feistiness"], "6.7 6.9 9.7": ["breakpoints"], "-1.6 1.4 10.8": ["glycemic"], "-4.2 16.0 3.7": ["organizationally"], "4.3 -2.7 2.0": ["titleholders"], "10.7 0.6 23.3": ["dockworkers"], "-3.3 -7.3 8.1": ["hairstyling"], "2.4 2.9 5.4": ["versioning"], "2.0 0.6 12.4": ["dishwashing"], "6.1 4.8 10.1": ["rectitude"], "5.2 9.7 6.8": ["cinders"], "-0.8 10.0 -4.7": ["disavows"], "3.4 5.3 3.2": ["ligands"], "14.8 -2.6 9.4": ["gawky"], "4.1 18.5 10.9": ["pretenses"], "15.2 9.9 12.7": ["raggedy"], "-6.4 8.5 7.5": ["dingers"], "19.1 4.1 15.3": ["funfair"], "-9.9 4.4 1.1": ["elapse"], "5.0 18.6 12.6": ["possessor"], "11.5 7.8 11.8": ["holidaymaker"], "11.0 -3.2 6.1": ["flexi"], "7.8 13.9 2.4": ["buffing"], "3.9 3.3 10.5": ["skims"], "-3.0 12.4 2.4": ["dehydrate"], "-1.9 6.2 8.7": ["multimode"], "9.5 9.9 24.9": ["wallabies"], "-2.6 10.1 -3.8": ["handsfree"], "4.0 9.7 1.7": ["analogues"], "-1.8 2.0 12.7": ["laminating"], "3.9 4.9 2.3": ["welled"], "4.2 2.4 10.7": ["tae"], "-1.4 3.6 7.4": ["bedsores"], "10.1 1.1 28.8": ["plantain"], "0.4 19.9 9.2": ["illiberal"], "7.9 -3.4 2.4": ["campuswide"], "3.4 3.7 -1.7": ["shunting"], "8.9 11.7 8.0": ["unpromising"], "17.7 6.8 2.0": ["jubilantly"], "10.6 6.4 14.8": ["settee"], "-2.1 12.0 9.6": ["pronouns"], "3.6 10.4 7.8": ["dullness"], "12.7 1.2 9.2": ["kazoo"], "18.9 7.0 7.8": ["geezers"], "10.0 10.5 9.0": ["yips"], "13.0 6.1 3.1": ["backtracks"], "7.4 2.2 13.2": ["microblog"], "3.1 1.9 33.0": ["mangos"], "12.2 14.7 13.0": ["obligingly"], "6.8 9.7 9.8": ["rivet"], "5.3 20.7 7.0": ["punchers"], "3.9 6.6 13.0": ["tapper"], "3.2 11.8 10.2": ["oddballs"], "6.0 22.6 18.5": ["adventuring"], "3.5 4.4 13.2": ["necrosis"], "3.2 5.1 47.2": ["bonito"], "10.8 7.4 14.9": ["hobbles"], "-7.0 9.5 11.0": ["concealer"], "-9.6 4.2 1.3": ["extraditions"], "-0.5 17.6 11.1": ["crosswind"], "5.7 9.3 5.3": ["newswires"], "4.6 7.5 9.6": ["oxygenated"], "6.9 16.2 15.7": ["bonobos"], "21.8 12.5 15.2": ["hobbits"], "8.0 8.1 15.4": ["dropper"], "7.2 0.0 3.1": ["separators"], "3.6 10.5 9.4": ["brazenness"], "11.1 6.7 9.3": ["constipated"], "4.9 7.5 1.1": ["menorahs"], "2.5 9.5 10.4": ["aphorisms"], "14.0 9.6 23.3": ["steamers"], "0.9 18.6 8.4": ["audibles"], "0.7 4.6 11.5": ["soca"], "3.4 9.5 3.4": ["philanthropies"], "5.5 5.2 19.4": ["chan"], "6.5 -3.4 -1.9": ["bode"], "-0.4 3.7 10.6": ["nit"], "14.2 11.9 12.7": ["fiddly"], "7.9 7.2 7.2": ["carbonates"], "0.9 9.6 -0.2": ["deregister"], "15.8 8.9 7.4": ["paperweight"], "-0.9 7.5 11.3": ["pathologic"], "9.0 6.4 8.0": ["gurneys"], "9.8 8.3 1.6": ["strapline"], "1.9 1.7 1.8": ["lockable"], "9.4 11.8 13.8": ["closeup"], "-1.7 3.0 2.8": ["policewomen"], "5.6 16.9 5.3": ["outfoxed"], "1.3 10.9 8.2": ["diffident"], "4.7 10.7 11.8": ["forestalling"], "6.3 8.5 -4.2": ["cloakroom"], "3.8 5.9 4.9": ["heatedly"], "3.6 11.7 9.6": ["wearying"], "8.7 2.8 -1.6": ["braille"], "9.7 8.4 9.1": ["bedspread"], "-0.6 7.0 7.5": ["hemming"], "16.0 4.4 5.9": ["ful"], "-2.5 3.7 4.8": ["essayed"], "7.4 4.6 10.6": ["welt"], "13.0 7.6 5.0": ["accumulator"], "6.5 0.8 6.1": ["emptier", "shacking"], "-5.4 2.1 -4.0": ["hardwork"], "1.3 3.0 11.0": ["urethane"], "20.4 4.3 8.6": ["rethinks"], "1.8 4.8 3.2": ["sniffling"], "1.5 11.3 5.3": ["motorcades"], "-8.1 0.8 23.3": ["marbling"], "8.4 25.5 10.5": ["imbecile"], "12.6 -2.4 4.2": ["deconsolidation"], "7.8 3.8 29.4": ["fjords"], "8.7 4.4 4.8": ["gauche"], "4.7 6.0 6.4": ["sooooo"], "4.8 -2.2 5.2": ["pullouts"], "0.9 8.2 8.1": ["byway"], "5.0 -4.3 8.0": ["bustles"], "0.8 18.8 -0.7": ["debase"], "17.8 4.7 18.8": ["jiggling"], "0.6 6.4 8.8": ["balladeer"], "2.4 5.9 8.8": ["hoopsters"], "-8.1 17.8 5.3": ["unchurched"], "1.7 8.0 2.4": ["hermetic"], "8.7 10.3 10.4": ["sinew"], "-8.5 -0.2 9.9": ["psf"], "-2.0 9.5 10.8": ["legging", "crosscheck"], "7.0 -2.6 10.2": ["popemobile"], "2.3 1.4 6.4": ["shoplifted"], "-1.7 9.1 2.9": ["bootlegged"], "8.7 5.9 5.7": ["foisting"], "7.4 8.7 -1.5": ["excrete"], "-2.6 8.5 7.5": ["possibles"], "0.2 10.7 11.1": ["erlotinib"], "11.6 13.1 11.2": ["memes"], "4.0 21.1 7.1": ["bikie"], "-4.5 4.9 -1.0": ["ascribes"], "-0.4 10.3 16.8": ["joists"], "0.8 1.6 6.6": ["longhand"], "-9.6 6.2 -0.6": ["therapeutically"], "3.3 2.6 8.7": ["ru"], "2.6 6.8 8.8": ["accordionist"], "12.8 23.4 19.1": ["wuss"], "18.5 6.0 15.4": ["teardrop"], "8.0 16.5 12.3": ["strobe"], "14.2 16.1 12.8": ["feebly"], "12.4 21.7 6.4": ["feint"], "18.1 16.2 13.9": ["splattering"], "15.7 4.6 11.6": ["crushers"], "-1.8 11.2 22.4": ["overcook"], "4.2 15.5 1.5": ["reacquire"], "-2.7 11.0 4.6": ["orebody"], "12.7 11.6 12.5": ["smothers"], "6.1 4.1 7.4": ["wth"], "2.7 7.4 3.3": ["deg"], "0.8 3.7 11.6": ["bussing"], "6.9 15.2 4.1": ["enchant"], "-3.3 9.6 13.7": ["buildable"], "18.1 9.8 16.7": ["whimsically"], "-10.5 3.2 5.3": ["hysterectomies"], "-3.2 15.1 25.8": ["whitetail"], "8.7 5.1 6.6": ["testbed"], "0.1 12.0 5.0": ["defecation"], "6.7 13.5 11.9": ["molesters", "pillions"], "0.8 -0.1 28.9": ["tangerines"], "-4.5 -0.1 4.6": ["nonmedical"], "25.4 14.3 16.6": ["splat"], "3.9 9.8 16.6": ["yachtsmen"], "4.4 3.1 44.7": ["pompano"], "4.9 16.6 1.6": ["untrammeled"], "-0.2 7.4 7.2": ["associative"], "19.0 13.1 4.8": ["nettlesome"], "1.1 12.1 44.9": ["wahoo"], "11.0 4.4 5.3": ["bathrobes"], "-6.3 5.7 0.5": ["errs"], "6.5 4.3 5.3": ["physiques"], "13.4 8.8 8.5": ["disassembling"], "-1.2 12.0 6.0": ["codefendant"], "0.1 10.0 11.8": ["tadalafil"], "4.7 17.3 9.4": ["blurts"], "-0.4 16.5 16.4": ["courtesan"], "18.0 22.0 17.3": ["squish"], "2.9 4.4 2.6": ["quadrangular"], "-5.3 -4.4 2.8": ["nonwovens"], "0.3 19.9 9.6": ["adulterer"], "-1.0 1.7 13.2": ["microchipping"], "10.5 3.5 5.4": ["revolved"], "4.5 7.8 35.1": ["sourdough"], "1.6 10.8 5.8": ["postulates"], "-3.8 10.5 8.7": ["grittiness"], "5.3 9.1 -1.1": ["ventilating"], "-4.2 2.3 4.1": ["dh"], "16.6 2.6 6.9": ["cantilevered"], "5.4 0.2 37.8": ["linguine"], "11.1 1.3 6.0": ["lifespans"], "12.7 11.2 15.1": ["juke"], "5.8 8.5 -0.7": ["geotagging"], "4.3 14.9 16.0": ["crybaby"], "8.2 2.2 12.7": ["cappuccinos"], "-8.1 -4.7 1.1": ["antenatal"], "2.0 2.1 28.0": ["pickling"], "0.7 -1.6 9.8": ["choristers"], "9.3 17.4 22.8": ["pansy"], "7.6 10.8 7.6": ["flubs"], "4.3 2.9 3.6": ["regaling"], "2.2 11.8 23.1": ["tartar"], "-1.6 9.2 -0.7": ["cohesively"], "-1.6 -0.1 19.5": ["brunches"], "-3.4 4.2 15.7": ["crewing"], "2.2 6.0 -5.6": ["regurgitation"], "2.9 21.8 21.4": ["swordplay"], "20.7 16.9 31.1": ["spiny"], "11.6 2.9 18.5": ["hatted"], "-7.0 -0.4 3.2": ["videography"], "9.7 9.1 0.9": ["confusingly"], "7.0 20.7 7.7": ["wizarding"], "7.8 8.6 6.8": ["hashtag"], "4.3 9.1 3.7": ["orderliness"], "7.4 3.7 3.8": ["itunes"], "-1.0 11.6 4.5": ["unreturned"], "-7.2 2.9 3.4": ["esthetician"], "0.4 0.5 12.9": ["racquets"], "1.3 2.9 5.8": ["yuh"], "16.5 -0.1 12.9": ["gorged"], "2.9 -6.8 2.9": ["podiatry"], "-3.8 7.5 -0.0": ["zakat"], "-6.7 19.5 3.6": ["confidences"], "5.2 5.8 10.7": ["dawdling"], "-3.3 14.2 -1.6": ["aerodrome"], "-1.6 6.5 6.3": ["abrasives"], "1.6 11.2 9.4": ["antifungal"], "6.4 7.0 4.7": ["newsdesk", "sticksman"], "1.0 3.8 11.5": ["underfed"], "9.1 5.8 4.8": ["unexceptional", "dizzyingly"], "13.2 0.2 18.4": ["nkr"], "-4.7 14.0 3.6": ["undershirt"], "5.8 4.4 8.1": ["hairbrush"], "10.8 0.5 24.1": ["taffy"], "0.9 11.8 7.0": ["snr"], "-3.8 8.8 14.0": ["anthropogenic"], "9.4 11.5 6.9": ["liquefy"], "5.4 -2.9 5.1": ["scrounged"], "6.5 15.6 4.6": ["unmindful"], "-5.2 2.3 4.0": ["comorbidities"], "8.4 7.6 -0.6": ["tunneled"], "4.7 7.9 -1.6": ["absolves"], "3.8 19.1 11.5": ["actioner"], "-1.3 12.4 10.2": ["anxiousness"], "12.7 19.2 3.4": ["gunslingers"], "10.6 -3.3 4.4": ["homepages"], "14.5 9.9 8.1": ["metronome"], "-2.3 11.7 -3.3": ["virally"], "-5.4 8.7 5.5": ["subregional"], "-1.0 2.5 6.4": ["vitiligo"], "-9.6 0.3 1.2": ["redrafted"], "-2.6 1.8 4.6": ["injectables"], "4.1 -3.2 11.3": ["waitressing", "kel"], "-1.0 3.7 16.9": ["synchro"], "5.8 12.0 3.1": ["dramatizing"], "10.7 18.8 7.9": ["sociopaths"], "0.9 8.3 -1.4": ["recapitalized"], "2.2 -3.1 5.4": ["ted"], "1.2 4.7 4.8": ["pageviews"], "13.1 -1.5 7.6": ["natty"], "3.7 2.1 15.3": ["slaloms"], "7.8 7.9 8.0": ["elongate"], "3.8 13.7 4.5": ["sunniest"], "-5.5 -3.7 5.2": ["intramurals"], "9.5 6.0 11.7": ["erasers"], "-1.4 1.9 20.7": ["longboard"], "0.2 8.8 6.7": ["bossing"], "9.2 5.8 6.1": ["roadies"], "-2.5 10.2 6.5": ["cantonments"], "4.2 6.7 4.0": ["payphones"], "20.0 10.6 14.1": ["amigos"], "13.8 3.0 11.5": ["dimpled"], "-2.1 7.3 9.5": ["nondistrict"], "19.5 14.5 4.8": ["stupefying"], "4.8 13.3 2.1": ["inflames"], "4.2 12.8 0.1": ["doggedness"], "-5.0 2.2 -0.1": ["mainstreamed"], "-2.7 6.5 -0.5": ["snom"], "5.1 0.1 9.9": ["trombones"], "3.9 17.7 10.9": ["homies"], "3.3 8.9 12.9": ["preheat"], "0.9 4.5 8.9": ["sarcoidosis"], "19.4 2.8 5.2": ["quadruples"], "11.8 5.5 6.9": ["bleeps"], "11.8 -0.4 5.1": ["wend"], "9.3 12.4 19.3": ["scrapper"], "2.6 2.9 8.9": ["standpipe"], "-8.0 2.4 8.1": ["capecitabine"], "13.6 1.9 5.2": ["thursday"], "21.6 10.7 7.7": ["featureless"], "-3.8 5.2 4.9": ["developable"], "3.7 15.1 5.1": ["exorcist"], "15.4 2.5 22.5": ["parakeets"], "4.1 14.6 4.3": ["predestined"], "0.5 6.4 3.9": ["upsell"], "-3.3 9.7 18.4": ["roadbed"], "9.7 17.6 10.5": ["leper"], "-0.6 12.1 17.2": ["hooch"], "10.6 16.2 4.2": ["trapdoor"], "1.8 8.7 13.5": ["disarmingly"], "12.2 7.7 15.4": ["gouges"], "1.2 16.2 12.9": ["dojo"], "10.1 3.2 7.8": ["preen"], "4.1 4.1 -4.8": ["outsprinted"], "9.4 9.4 -0.1": ["magnetically"], "21.3 12.7 23.0": ["goop"], "2.2 6.6 17.3": ["broil"], "2.1 11.9 4.3": ["unobtainable"], "-1.6 13.9 -2.0": ["indiscreet"], "5.5 10.0 5.3": ["seethe"], "11.7 2.5 1.5": ["ruffling"], "-13.4 9.4 24.0": ["antlerless"], "6.6 7.2 12.0": ["stagnates"], "15.9 3.3 23.3": ["pinkish"], "1.5 7.4 4.2": ["seismological"], "8.2 10.6 5.1": ["oscillate"], "0.3 4.4 5.7": ["knowledgebase"], "3.4 10.8 6.8": ["impregnate"], "7.6 3.2 4.5": ["workin"], "6.4 7.6 12.2": ["cockfight"], "12.6 18.2 8.8": ["pounces"], "-4.5 13.6 4.2": ["lymph"], "4.8 3.5 6.9": ["recommenced"], "-6.0 3.7 4.6": ["walkability"], "-0.3 19.1 5.0": ["sprit"], "1.4 14.7 2.5": ["extinguishers"], "0.8 17.7 7.6": ["carjackers"], "5.2 5.2 -1.0": ["bumbled"], "4.3 1.3 -1.8": ["unaccredited"], "3.6 8.7 23.4": ["mojito"], "-4.3 11.2 8.1": ["adenocarcinoma"], "12.0 5.4 5.1": ["burping"], "16.6 18.9 13.1": ["chimera"], "-1.6 18.4 7.1": ["exacts"], "-3.4 4.5 13.8": ["vestry"], "6.8 13.7 12.4": ["pugilists"], "20.3 14.7 12.9": ["buzzards"], "4.3 -2.8 16.0": ["noodling"], "7.5 16.6 25.1": ["mariner"], "15.2 3.6 1.1": ["sooth"], "10.6 11.0 19.0": ["magnolias"], "-2.0 7.5 12.1": ["mishit"], "-3.1 1.3 7.2": ["talkback"], "-1.4 17.4 10.4": ["putout"], "-3.4 2.4 8.3": ["topologies"], "21.8 8.0 10.0": ["moonscape"], "2.5 1.0 18.7": ["organza"], "-10.1 2.3 6.0": ["multihit"], "7.9 -3.5 9.1": ["sc"], "1.6 21.6 9.0": ["afghan"], "-3.0 16.1 5.6": ["heartbreakingly"], "4.1 9.8 2.6": ["repairers"], "-0.9 6.2 17.9": ["legume"], "-2.4 1.2 5.3": ["invalidation"], "2.7 2.6 17.5": ["jeepney"], "1.3 11.9 26.8": ["upwelling"], "0.2 10.5 0.3": ["recuperates"], "0.7 6.2 14.8": ["rasp"], "3.8 5.1 12.8": ["filmy"], "3.6 6.6 6.5": ["elan"], "14.9 16.2 10.8": ["prowls"], "18.8 6.8 15.4": ["hirsute"], "-0.5 2.3 0.3": ["inclusivity"], "12.2 5.5 14.3": ["washington"], "18.2 5.8 12.9": ["seesawing"], "2.8 7.6 0.0": ["dysfunctions"], "9.5 6.3 13.1": ["portents"], "-1.1 12.0 10.1": ["adulterers"], "-1.7 12.8 10.8": ["scintilla"], "4.5 -3.0 -4.8": ["acquits"], "11.5 -1.7 11.4": ["placemats"], "21.4 3.1 26.0": ["bellied"], "27.3 12.6 27.3": ["dino"], "3.0 6.5 6.4": ["qb"], "5.6 -3.6 9.6": ["baled"], "-3.1 10.2 11.1": ["trailheads"], "-2.3 8.8 8.1": ["headman"], "8.9 7.3 8.2": ["quotidian"], "6.2 5.5 8.3": ["diverticulitis"], "5.9 4.3 8.8": ["snorts"], "14.0 11.4 11.0": ["quicksilver"], "19.6 1.8 2.2": ["unrolled"], "16.9 16.2 13.7": ["doofus"], "6.0 0.9 12.2": ["orlistat"], "0.7 8.7 3.3": ["impinging"], "0.0 9.7 15.1": ["mulched"], "0.1 2.2 28.0": ["charcuterie"], "0.9 20.2 27.1": ["aphid"], "22.8 27.3 9.0": ["sentinels"], "-1.8 9.0 19.9": ["forestlands"], "-8.2 -0.8 13.6": ["nom"], "19.5 5.2 7.1": ["bedazzled"], "11.1 14.0 11.7": ["effing"], "0.9 6.8 1.8": ["operationalization"], "11.1 -2.3 8.3": ["june"], "2.9 16.1 0.6": ["embarassment"], "12.0 4.7 3.0": ["ninemsn"], "7.5 1.3 5.8": ["easels"], "0.1 3.0 5.4": ["filesystem"], "9.2 10.4 -2.0": ["hairdryer"], "-0.9 10.5 8.5": ["interdepartmental"], "-7.7 21.3 9.0": ["carbine"], "-1.8 8.8 3.6": ["gendered"], "2.2 11.0 10.5": ["blunts"], "3.2 9.7 4.6": ["regurgitating"], "10.6 14.5 7.9": ["airlock", "bubbleheads"], "-0.3 9.9 6.4": ["couplet"], "2.1 2.1 8.4": ["dulcimer"], "24.4 3.9 18.1": ["platypus"], "10.8 3.2 9.0": ["befuddling"], "-3.4 -1.8 -3.9": ["toxicological"], "-2.3 -3.1 15.5": ["nga"], "-7.0 22.2 -0.1": ["perpetration"], "-2.3 14.0 3.4": ["outshoot"], "-7.2 5.6 -2.7": ["standpoints"], "-0.3 4.8 30.3": ["marinara"], "4.4 7.2 25.4": ["alder"], "-1.5 16.4 3.7": ["scapegoated"], "-3.9 -3.7 6.9": ["bc"], "8.5 4.7 13.8": ["pipers"], "22.5 6.0 18.0": ["hippopotamus"], "0.2 9.8 -3.4": ["diff"], "1.7 12.0 -1.9": ["reintegrating"], "4.3 6.2 0.4": ["incompatibilities"], "3.0 7.2 10.7": ["skittishness"], "6.3 10.5 20.8": ["sloughs"], "2.2 10.5 4.3": ["strep"], "4.1 5.9 4.6": ["unsurprised"], "7.6 1.6 -0.8": ["schlep"], "6.6 5.8 0.7": ["trooping"], "1.5 13.4 4.9": ["disgracefully"], "13.1 4.6 6.0": ["shimmers"], "9.8 4.8 10.8": ["papermaking"], "9.9 8.7 11.0": ["chillin"], "-1.6 11.2 11.3": ["backpass"], "9.7 14.3 2.5": ["quiescent"], "8.5 12.5 14.4": ["weathermen"], "0.9 10.7 11.8": ["chelsea"], "-4.2 -5.7 4.3": ["compered"], "17.4 2.8 12.1": ["olympic"], "-1.7 26.5 8.5": ["chauvinist"], "-7.7 11.2 7.9": ["ecumenism"], "-1.4 13.5 1.3": ["possiblity"], "-7.5 3.0 1.3": ["platted"], "8.3 7.3 -1.5": ["coder"], "1.5 11.1 8.5": ["rightward"], "-8.0 5.4 2.5": ["appealable"], "6.2 6.6 3.2": ["varsities"], "-8.9 1.1 7.9": ["oscilloscopes"], "3.6 7.0 10.2": ["crematoriums"], "-10.3 4.7 3.6": ["rheumatologist"], "5.5 -4.1 14.4": ["leis"], "-6.1 0.8 4.0": ["depute"], "8.6 7.1 9.9": ["loafing"], "12.9 7.3 7.8": ["malarkey"], "0.8 13.9 15.4": ["musk"], "14.8 10.4 9.1": ["lookalikes"], "18.0 0.1 12.1": ["wackiest"], "0.4 6.7 37.5": ["gazpacho"], "14.7 5.8 7.0": ["blackboards"], "-2.1 9.3 6.7": ["acclimation"], "11.4 12.2 6.8": ["orgasmic"], "6.2 3.3 10.5": ["carbonation"], "1.7 10.8 9.7": ["snippy"], "6.5 3.6 12.8": ["shooing"], "10.9 6.1 17.5": ["rafter"], "1.8 10.5 4.0": ["rediscovers"], "6.6 12.0 16.8": ["gangway"], "12.6 0.4 3.4": ["forecourts"], "10.6 26.5 17.5": ["wiles"], "3.2 5.4 4.4": ["phenotypes"], "-5.0 15.5 2.2": ["inborn"], "13.6 15.7 13.6": ["perching"], "-1.4 12.3 5.8": ["debasing"], "7.1 1.9 6.9": ["stockyards"], "-2.6 15.6 1.7": ["flatters"], "-3.0 12.3 7.6": ["macula"], "5.5 7.7 9.8": ["communally"], "9.9 8.9 -0.2": ["cudgels"], "4.1 11.6 -0.3": ["democratized"], "-9.7 6.3 5.1": ["pioglitazone"], "1.7 10.8 18.2": ["magnum"], "4.6 12.3 25.4": ["pestle"], "7.9 7.8 6.3": ["progenitors"], "-8.7 17.4 1.8": ["adjutant"], "16.1 7.0 10.4": ["glinting"], "2.7 8.2 3.3": ["texters"], "12.4 0.6 23.6": ["woodchips"], "2.9 2.4 -0.7": ["ventricles"], "-3.7 5.2 14.0": ["pectin"], "8.9 5.2 15.7": ["refloat"], "3.7 10.3 10.0": ["misanthropic"], "8.2 12.2 -1.5": ["numeral"], "5.8 3.0 9.9": ["snowbanks"], "11.1 21.0 6.8": ["redoubt"], "7.4 16.7 10.9": ["seductress"], "-8.4 9.9 3.4": ["lucidity"], "17.7 9.5 20.4": ["glutton"], "-4.4 5.2 11.4": ["astrocytes"], "1.0 11.1 11.2": ["inauthentic"], "18.5 -2.7 6.4": ["quintuple"], "-5.5 2.4 2.6": ["roadworthy"], "7.5 21.9 21.0": ["scurvy"], "-8.1 11.4 24.0": ["basmati"], "-8.1 5.3 -1.4": ["retuned"], "14.9 19.0 11.9": ["temptress"], "5.5 12.3 28.3": ["specie"], "11.2 16.5 18.6": ["yob"], "8.8 -0.4 0.1": ["googled"], "12.8 22.8 1.2": ["relentlessness"], "5.3 -3.2 13.5": ["eps"], "6.4 4.0 6.9": ["sulked"], "12.9 7.5 4.9": ["mortifying"], "15.9 15.0 8.2": ["manfully"], "7.3 9.3 11.6": ["exclamations"], "11.1 12.1 5.3": ["firmest"], "16.5 4.5 4.2": ["vibrated"], "4.8 1.6 8.9": ["exhibitionism"], "16.3 8.1 7.0": ["loping"], "-5.2 20.2 6.7": ["quartermaster"], "17.5 11.4 21.8": ["bluest"], "5.2 4.4 1.5": ["harken"], "16.8 10.2 9.1": ["shimmying"], "4.5 3.4 13.6": ["ruminants"], "-0.4 13.4 0.2": ["someway"], "1.8 5.6 18.8": ["toque"], "-2.6 6.5 -3.7": ["preoccupy"], "10.9 -3.6 2.1": ["razzmatazz"], "3.0 21.4 7.3": ["collectivist"], "12.3 18.9 10.6": ["pulverizing"], "-2.7 9.3 9.0": ["prospectivity"], "2.5 1.3 8.5": ["overproduced"], "-4.3 12.8 12.8": ["effluents"], "1.0 6.6 11.8": ["singleton"], "7.7 -0.5 17.8": ["sapphires"], "3.1 8.4 7.2": ["lignin"], "2.0 -8.4 3.9": ["crams"], "3.4 -1.7 14.5": ["frontside"], "10.6 14.0 9.4": ["audaciously"], "13.3 7.9 6.4": ["decliner"], "3.3 8.4 2.9": ["buttressing"], "-2.8 4.7 1.3": ["subsections"], "8.7 10.6 2.4": ["lux"], "9.3 1.7 6.5": ["parlaying", "interactives"], "8.7 7.3 13.0": ["stoners"], "3.4 14.6 1.1": ["unsmiling"], "7.5 18.4 5.7": ["supposing"], "1.4 13.0 -9.9": ["unprompted"], "9.8 9.9 4.7": ["tonics"], "8.6 8.8 8.6": ["freeform"], "0.7 6.9 13.8": ["abates"], "5.6 15.8 8.2": ["apparatchiks"], "18.3 11.8 20.0": ["wildebeest"], "3.3 2.3 28.0": ["samosas"], "3.0 1.8 0.6": ["administrating"], "10.0 12.9 5.9": ["blindfolds"], "4.1 23.5 3.2": ["nutcase"], "5.0 5.1 13.5": ["lozenges"], "7.7 -1.2 1.3": ["flameout"], "-2.0 3.4 2.7": ["redact"], "0.2 2.4 23.2": ["endosulfan"], "-3.4 0.9 -8.6": ["vouching"], "16.5 0.4 8.3": ["tubby"], "3.8 3.9 24.8": ["reefer"], "11.0 9.9 9.6": ["acrid"], "7.5 7.9 4.0": ["wikipedia"], "6.9 -3.5 -2.4": ["assuaging"], "-2.5 7.1 5.1": ["muddies"], "10.2 5.5 0.4": ["nonstandard"], "-4.5 1.5 -1.0": ["substantiating"], "13.7 10.1 15.4": ["trashcan"], "6.6 12.9 31.3": ["hydrangea"], "3.0 6.2 8.6": ["loci"], "8.2 6.9 8.3": ["confederations"], "4.4 0.7 14.2": ["testicular"], "-0.6 2.5 25.9": ["saltier"], "22.4 14.4 10.3": ["mimes"], "-2.6 4.8 6.1": ["biosimilar"], "5.2 3.3 11.1": ["scott"], "-3.1 1.2 9.8": ["femoral"], "-6.2 15.4 -0.7": ["ret"], "-4.6 12.0 1.8": ["nonjudgmental"], "-3.1 3.3 7.6": ["biopics"], "8.4 14.4 2.1": ["unbounded"], "14.1 3.4 28.5": ["enchilada"], "4.2 18.5 3.5": ["defaulter"], "15.3 4.3 8.9": ["whirlpools"], "3.1 8.0 19.2": ["dogwoods"], "-0.5 0.1 5.2": ["exenatide"], "-2.8 6.6 5.5": ["frugally"], "9.4 4.6 -2.1": ["whiles"], "0.4 -3.5 13.0": ["plainer"], "-4.6 7.7 27.6": ["camellias"], "2.1 2.1 -3.1": ["reconfirms"], "-0.5 12.8 5.4": ["indefinable"], "9.7 16.9 13.8": ["bobby"], "7.9 8.2 14.7": ["kneading"], "5.4 3.6 8.1": ["lockouts"], "-0.2 12.5 5.1": ["prognoses"], "-3.1 10.4 10.3": ["delineates"], "6.0 14.0 4.9": ["deliriously"], "7.4 12.1 7.4": ["bogged"], "5.2 4.1 7.9": ["hd"], "4.3 12.9 6.1": ["relearning"], "-3.5 12.6 13.5": ["watercourses"], "1.6 13.5 18.5": ["amulets"], "-1.9 -1.3 3.6": ["relator"], "-3.0 1.1 -4.6": ["indepth"], "11.2 1.7 1.1": ["wastebasket"], "5.7 9.3 15.3": ["aloe"], "5.5 5.1 4.7": ["applet"], "-2.6 1.0 10.4": ["cyclosporine"], "-0.9 7.2 -1.8": ["tendentious"], "-5.0 -8.1 -0.1": ["honoraria"], "12.8 11.4 9.4": ["braying"], "-1.1 6.3 -4.2": ["overemphasized"], "3.1 9.9 6.5": ["gearshift"], "2.3 13.6 6.2": ["exoplanet"], "-11.8 7.9 3.3": ["colorist"], "0.9 13.4 4.4": ["pulldown"], "3.3 7.2 3.9": ["epiphanies"], "-3.9 1.6 6.0": ["cityhood"], "21.5 5.2 3.6": ["whir"], "5.9 4.6 12.4": ["bingeing"], "8.1 11.3 11.3": ["disgustingly"], "1.8 12.6 22.8": ["wolverines"], "11.0 2.1 3.9": ["texas"], "14.8 15.2 3.2": ["guzzlers"], "1.8 7.8 9.8": ["nada"], "12.2 5.9 4.6": ["lothario"], "0.5 15.8 4.4": ["jealousies"], "-9.1 12.1 5.6": ["rotorcraft"], "3.9 14.3 8.5": ["balloonists"], "18.7 25.1 11.1": ["weakling"], "8.4 2.9 1.8": ["smoggy"], "12.1 7.5 12.8": ["prehistory"], "9.5 -0.5 11.4": ["bankrolls"], "-2.3 5.9 6.2": ["conditionalities"], "8.4 18.3 3.1": ["wackos"], "17.0 9.9 6.9": ["hewn"], "11.9 6.0 2.9": ["purred"], "10.9 2.9 15.2": ["steve"], "5.5 12.5 9.5": ["modding"], "0.7 1.3 9.9": ["barebones"], "1.6 13.3 5.2": ["perseveres"], "6.1 12.8 11.6": ["balletic"], "-1.1 6.3 10.6": ["generalists"], "10.4 8.0 6.4": ["countess"], "2.4 6.5 7.7": ["pileups"], "1.8 7.4 3.1": ["broaching"], "10.1 2.5 6.4": ["stimulator"], "-0.3 0.8 10.5": ["backdate"], "3.4 6.5 -6.6": ["assignee"], "-1.0 4.8 1.8": ["supermini"], "7.9 6.2 14.0": ["unctuous"], "5.4 14.1 -2.6": ["tribune"], "1.8 7.8 6.0": ["undercounted"], "9.9 -5.5 18.8": ["ming"], "11.7 2.2 7.3": ["phenoms"], "-0.3 6.5 6.2": ["patella"], "4.6 3.7 1.6": ["neatest"], "-0.6 4.9 6.9": ["scuff"], "6.8 7.0 1.4": ["immodest"], "11.0 19.2 2.2": ["counterpunch"], "-6.1 5.2 -3.8": ["agonists"], "3.1 7.9 5.0": ["unready"], "6.7 3.1 17.8": ["huskies"], "-3.9 -3.0 11.8": ["multisport"], "11.0 18.0 4.0": ["mobbing"], "3.6 3.6 11.6": ["chillier", "encoring"], "7.9 9.3 14.7": ["ow"], "3.2 18.9 5.2": ["disparagement"], "2.6 5.8 7.8": ["dir"], "-2.3 7.2 -4.5": ["bromide"], "13.2 21.6 5.3": ["corporatist"], "-5.6 -3.9 10.9": ["reimposed"], "-1.5 3.4 8.2": ["wakeboard"], "-10.1 0.8 9.8": ["weatherize"], "3.6 15.4 -0.9": ["discomforting"], "-10.6 6.4 -1.3": ["subspecialty"], "4.8 13.8 9.7": ["homescreen"], "4.0 8.8 9.0": ["tracklist"], "2.3 18.3 8.8": ["materialist"], "4.7 12.5 5.5": ["comm"], "-6.5 7.6 11.0": ["printmaker"], "-0.2 7.5 9.0": ["overstocked"], "11.9 12.0 21.7": ["boughs"], "-8.7 -4.9 3.1": ["cosmetologist"], "-2.4 -0.4 17.4": ["spicier"], "6.9 13.8 5.2": ["satirists"], "7.9 10.4 2.6": ["cyclicals"], "4.9 7.2 4.3": ["ballboy"], "7.5 1.4 8.4": ["incongruent"], "14.2 -5.9 9.8": ["koo"], "-4.9 4.9 10.5": ["barbiturates"], "8.2 10.5 -3.7": ["resound"], "0.7 6.4 10.0": ["godparents"], "8.3 10.3 8.5": ["hailstorms"], "-6.6 16.1 1.9": ["confidantes"], "-4.3 1.7 12.0": ["convents"], "14.8 12.1 7.0": ["inextricably"], "-14.2 7.3 21.4": ["palay"], "2.0 6.3 3.9": ["pined"], "12.5 1.9 1.7": ["outclassing"], "2.2 18.1 -0.4": ["unverifiable"], "9.8 13.2 0.4": ["asunder"], "10.6 7.2 13.1": ["preventer"], "11.6 11.5 1.2": ["tiremaker"], "-5.6 5.7 0.1": ["knowledgable"], "3.0 2.6 13.4": ["autoclave"], "-0.6 22.5 19.9": ["submariners"], "8.3 2.9 1.2": ["rubbishes"], "2.5 14.0 -2.6": ["rewinding"], "9.7 6.0 5.9": ["voyeurs"], "18.1 14.6 10.1": ["pummels"], "7.2 7.5 3.2": ["defecated"], "18.3 19.7 14.5": ["gnat"], "11.1 7.1 10.6": ["gobbledygook"], "7.8 2.9 10.2": ["pancaked"], "13.9 16.7 13.0": ["googly"], "11.5 10.2 10.4": ["ruination"], "9.1 9.8 10.0": ["birdsong"], "-5.1 9.9 7.5": ["sonnets"], "-1.3 6.5 1.2": ["hydroplaned"], "13.0 6.1 9.1": ["unlabeled"], "8.4 2.3 5.4": ["hipness"], "-5.0 -1.8 -1.3": ["formalization"], "7.7 35.2 17.4": ["deathmatch"], "10.5 13.7 3.0": ["swerves"], "5.1 4.5 28.9": ["chipotle"], "-4.9 2.9 7.5": ["charrette"], "11.9 18.6 6.5": ["egomaniac"], "-0.3 7.4 7.0": ["monsignor"], "-0.5 7.4 6.5": ["crypts"], "7.7 14.5 27.3": ["spooning"], "9.9 31.3 8.7": ["saboteur"], "-0.4 13.8 7.7": ["defunding"], "3.9 6.5 0.7": ["posers"], "12.9 -7.0 9.4": ["sashayed"], "5.6 7.5 20.1": ["nuptial"], "2.4 21.4 5.4": ["unchangeable"], "12.1 13.3 19.1": ["beanbag"], "-0.3 9.9 2.1": ["maximally"], "3.8 15.2 2.1": ["incase"], "-7.2 5.4 2.1": ["earphone"], "1.5 13.2 7.5": ["codefendants"], "20.2 8.8 25.9": ["pachyderm"], "6.1 3.2 9.8": ["rheumatism"], "4.8 4.6 2.2": ["seismology"], "2.0 4.2 6.0": ["zu"], "2.0 12.2 9.1": ["scudetto"], "2.2 4.4 4.8": ["synaptic"], "15.4 -1.7 10.1": ["april"], "3.0 9.1 1.9": ["inadvisable"], "4.1 3.7 0.8": ["ul"], "0.4 5.9 12.9": ["honeyed"], "6.7 20.6 9.5": ["repulsion"], "7.4 5.5 6.4": ["transpose"], "13.4 10.1 -0.5": ["nevermind"], "2.3 16.5 5.6": ["orchestrator"], "3.4 7.9 13.3": ["underarm"], "2.1 3.8 -5.4": ["outpourings"], "15.3 -2.9 6.3": ["newish"], "23.6 6.9 11.5": ["encase"], "8.9 18.3 11.4": ["vamps"], "2.0 9.7 15.4": ["gentry"], "18.2 3.5 9.7": ["piddling"], "7.1 16.5 6.9": ["misnamed"], "6.9 9.0 15.4": ["cleft"], "13.3 -0.8 4.6": ["tatty"], "11.6 1.3 8.3": ["larded"], "17.8 23.0 15.6": ["terminator"], "-3.2 1.1 8.1": ["chromatin"], "1.3 5.4 4.3": ["highpoint"], "3.4 12.5 9.8": ["divinely"], "-2.6 -6.0 6.7": ["phenol"], "-8.3 7.1 19.7": ["turfgrass"], "4.5 12.7 7.5": ["unbound"], "10.9 5.8 18.5": ["franks"], "9.1 -3.0 12.5": ["gr"], "-2.4 9.3 13.8": ["punchlines"], "3.2 8.3 18.1": ["crafter"], "1.5 9.9 -0.5": ["ravings"], "-1.6 9.2 -2.8": ["airside"], "10.3 2.4 2.5": ["sundries"], "13.2 4.1 5.8": ["humdinger"], "-10.6 13.4 8.1": ["chemotherapies"], "-1.9 4.3 3.1": ["glamorized"], "9.4 2.5 3.9": ["backstopping"], "-4.5 7.9 11.7": ["innkeepers"], "0.5 12.2 9.3": ["roguish"], "19.6 9.8 2.8": ["apotheosis"], "8.7 13.9 8.0": ["irrelevancy"], "16.3 4.7 13.1": ["limbed"], "22.0 17.8 19.4": ["leprechauns"], "7.0 -1.9 4.0": ["octogenarians"], "4.9 5.9 0.1": ["comparatives"], "3.6 -2.5 -1.0": ["overbooking"], "0.2 8.2 9.0": ["integer"], "5.1 11.7 5.0": ["scythed"], "6.2 10.6 4.0": ["wearied"], "3.1 6.0 9.7": ["breeches"], "18.2 8.2 10.0": ["concentric"], "7.1 6.6 11.9": ["campout"], "-7.4 18.4 -0.8": ["transgressed"], "-12.9 15.0 5.9": ["hadith"], "4.0 6.4 5.5": ["proficiently"], "18.9 0.8 0.2": ["eightfold"], "10.2 5.8 2.5": ["discoverers"], "0.6 5.2 14.5": ["appealingly"], "7.0 13.2 3.7": ["christians"], "-2.1 0.6 14.6": ["karat"], "4.0 7.2 9.8": ["torts"], "0.4 -1.1 4.3": ["dissertations"], "4.0 9.8 2.2": ["pandered"], "-5.6 10.2 -2.1": ["verbalize"], "-2.1 8.1 6.1": ["disgruntlement"], "11.0 13.9 17.4": ["barehanded"], "8.1 6.9 5.3": ["nanoseconds"], "0.6 10.5 7.6": ["creepiness"], "-0.6 -2.4 3.4": ["topnotch"], "4.3 20.1 2.3": ["fanatically"], "6.1 8.5 0.1": ["flouts"], "6.8 0.1 18.0": ["ai"], "17.4 6.1 24.3": ["parakeet"], "2.4 11.9 8.9": ["veld"], "7.6 6.3 3.3": ["liras"], "2.6 14.4 29.5": ["trollers"], "-0.9 20.0 9.4": ["salutation"], "4.2 8.1 4.5": ["requiem"], "7.4 9.2 -4.8": ["lusted"], "-4.2 5.6 13.5": ["diacetyl"], "2.1 16.8 1.4": ["borderlands"], "-1.2 7.2 6.5": ["livings"], "15.4 1.6 14.6": ["teepee"], "9.3 1.8 30.5": ["quayside"], "10.2 9.4 10.2": ["mangle"], "3.1 10.6 6.6": ["penitence"], "5.2 1.7 10.6": ["cattleman"], "-4.1 1.5 6.1": ["androgen"], "1.3 9.7 0.1": ["posession"], "3.0 0.1 4.0": ["opticians"], "7.9 15.5 5.9": ["unprecedentedly"], "-4.0 10.0 3.9": ["vaulters"], "14.2 15.1 10.4": ["grabbers"], "6.4 14.2 -2.4": ["unshaken"], "2.1 -5.7 -3.0": ["neurosciences"], "6.1 5.9 18.6": ["petroglyphs"], "1.4 -2.1 -1.5": ["schedulers"], "-8.2 2.3 -5.7": ["aver"], "-6.9 2.7 -8.9": ["maintainability"], "5.1 6.7 14.5": ["cilia"], "6.6 4.4 10.8": ["famers"], "-0.9 0.7 12.3": ["uncoated"], "16.0 16.6 15.1": ["tomahawk"], "-5.0 5.0 11.5": ["reimpose"], "-1.0 2.4 1.5": ["deregistered"], "-4.1 5.2 -4.9": ["powerplants"], "10.7 10.9 7.6": ["throb"], "10.3 23.1 -0.0": ["detractor"], "9.3 13.2 10.7": ["cocking"], "-4.3 11.7 3.9": ["inhibitory"], "-3.4 12.2 -4.6": ["uncharged"], "-10.8 10.6 1.6": ["evidential"], "-4.5 13.6 6.6": ["inactivation"], "-6.1 -1.0 9.1": ["denture"], "7.8 13.6 4.9": ["dullest"], "-8.1 -4.3 12.0": ["mellower"], "5.9 -3.3 8.6": ["della"], "8.6 8.2 11.5": ["pouty"], "-9.9 7.0 -1.0": ["smokefree"], "-8.1 1.1 13.0": ["flours"], "0.4 1.8 15.5": ["vesicles"], "7.9 10.0 24.1": ["bulkheads"], "9.8 8.6 11.6": ["souk"], "0.3 10.0 -1.1": ["embarassed"], "7.8 1.6 12.4": ["ju"], "8.7 1.8 6.2": ["stardust"], "-2.4 4.2 6.6": ["esthetics"], "0.8 9.0 9.2": ["chicanes", "recrystalizes"], "-7.0 -4.0 13.8": ["sentencings"], "2.9 6.4 9.6": ["sucralose"], "-6.3 0.2 5.3": ["reapplying"], "4.9 8.7 10.8": ["thermals"], "12.2 6.9 6.8": ["greenness"], "3.6 -1.3 12.5": ["postrace"], "7.9 16.3 9.5": ["kooks"], "2.4 10.1 8.5": ["emigrant"], "1.9 11.7 4.2": ["elegy"], "1.2 3.1 11.9": ["proteomic"], "-12.6 11.8 6.3": ["rangelands"], "-11.7 16.1 1.2": ["incapacitation"], "2.4 2.4 6.5": ["repriced"], "1.1 9.3 8.9": ["enzymatic"], "2.4 16.4 4.3": ["securitymen"], "-5.3 23.2 9.8": ["sinning"], "9.3 10.6 13.6": ["aerated"], "3.2 7.3 7.0": ["therefor"], "0.9 22.9 11.1": ["unitedly"], "8.4 23.0 11.1": ["sadist"], "18.9 6.5 8.9": ["encloses"], "-8.2 10.5 0.3": ["introspect", "intoxilizer"], "-1.7 8.7 1.7": ["nullity"], "-4.4 -4.9 3.5": ["subvention"], "18.3 21.3 6.1": ["loosed"], "0.8 17.9 15.8": ["lefthanders"], "-5.9 21.7 1.2": ["insinuates"], "-2.0 -2.0 4.6": ["suborbital"], "0.7 12.9 3.9": ["complementarity"], "6.8 5.2 7.0": ["peon"], "-0.7 17.1 3.9": ["unapproachable"], "2.3 11.8 8.3": ["calluses"], "15.3 8.1 12.9": ["runt"], "4.9 0.7 7.2": ["typefaces"], "11.5 17.5 14.8": ["loveliness"], "13.1 6.4 1.3": ["minimalistic"], "2.6 19.6 12.9": ["phonies"], "1.6 -0.9 4.6": ["birthdates"], "0.8 9.2 -0.8": ["acceptably"], "6.3 7.5 7.9": ["vex"], "-1.5 7.9 1.8": ["valuers"], "4.9 3.6 4.7": ["postcodes"], "0.5 11.3 7.2": ["eavesdropped"], "-1.6 6.2 5.1": ["revpar"], "3.8 4.0 11.5": ["ak"], "4.5 13.6 25.9": ["seaward"], "-1.2 1.6 5.5": ["orthodontics"], "5.7 8.6 12.3": ["burr"], "9.2 22.1 10.9": ["fearfully"], "3.9 15.1 5.7": ["kickboxer"], "9.0 2.5 15.6": ["woodcarving"], "-3.4 4.4 1.9": ["emulators"], "11.5 8.1 1.2": ["refocuses"], "8.8 10.9 16.6": ["hardier"], "7.6 2.7 15.2": ["calipers"], "2.9 2.4 11.6": ["tassel"], "6.2 9.1 44.2": ["seabird"], "6.9 4.7 8.8": ["pubescent"], "6.1 20.5 8.3": ["bioterror"], "11.5 7.5 13.2": ["figureheads"], "8.3 -0.5 14.1": ["boning"], "1.4 2.5 11.6": ["schmaltz"], "-9.2 6.3 5.2": ["osteosarcoma"], "7.9 19.8 10.2": ["telegraphing"], "-0.4 -0.1 3.7": ["vids"], "-5.2 14.1 8.0": ["telephoto"], "7.2 7.3 1.5": ["hows"], "-3.9 16.5 1.0": ["disrespects"], "0.7 7.3 9.8": ["bedsit"], "7.3 0.2 19.1": ["clapboard"], "3.2 -1.3 1.5": ["ent"], "9.1 13.8 6.3": ["scofflaw"], "1.8 8.0 6.9": ["pathfinder"], "-10.5 5.0 7.7": ["denims"], "1.3 0.8 2.2": ["geoscience"], "11.1 14.5 24.2": ["sundaes"], "1.9 9.9 0.4": ["interweaving"], "9.7 -0.6 4.7": ["gatecrash"], "-0.8 7.1 2.9": ["happend"], "1.6 9.2 12.5": ["heritages"], "9.1 0.3 12.0": ["uncork"], "-9.9 0.5 8.4": ["necklines"], "10.4 2.3 2.6": ["planeloads"], "-0.2 9.4 -3.4": ["rebuts"], "5.4 22.4 9.4": ["groupthink"], "4.7 3.1 9.6": ["melodramas"], "-0.4 11.3 -7.8": ["indemnified"], "-2.7 10.1 8.3": ["shader"], "-2.1 -0.2 32.9": ["balsamic"], "22.2 3.4 4.6": ["billows"], "5.1 9.0 14.2": ["calcified"], "-8.9 6.3 9.4": ["periodontal"], "6.5 11.2 16.2": ["somethin"], "2.5 1.6 1.7": ["turbocharging"], "10.7 14.8 6.4": ["deign"], "0.2 3.9 11.2": ["downscale"], "-2.2 17.8 8.7": ["ineffectively"], "2.3 14.5 0.9": ["pathologically"], "9.2 7.9 -0.1": ["magnetometer"], "1.5 -4.7 3.7": ["microfluidics"], "9.7 3.8 19.1": ["pagodas"], "8.8 6.2 7.9": ["spacewalker"], "10.8 11.5 9.0": ["juju"], "-0.6 6.7 4.1": ["tabulations"], "11.8 19.0 11.2": ["outermost", "supremist"], "9.4 11.3 13.4": ["birthmark"], "7.2 7.4 11.8": ["insouciance"], "3.9 17.2 2.1": ["parrying"], "1.9 7.5 10.6": ["tearjerker"], "-8.1 1.5 1.6": ["solemnized"], "-3.2 10.3 13.2": ["truants"], "7.8 9.7 10.6": ["anticlimax"], "-5.4 0.2 1.4": ["reexamined"], "-4.0 1.4 3.6": ["humourous"], "17.6 12.7 6.0": ["girded"], "18.0 13.3 6.9": ["dorks"], "20.3 20.3 20.4": ["exoskeleton"], "-2.0 -3.8 0.7": ["mmboe"], "-3.2 2.9 3.2": ["neurodegenerative"], "0.7 9.5 7.3": ["acupressure"], "7.7 5.3 -1.9": ["televangelists"], "19.3 13.2 9.1": ["skywards"], "8.3 6.5 14.2": ["cleaved"], "7.6 14.1 1.4": ["trigonometry"], "11.0 6.4 18.7": ["soupy"], "-1.6 -0.6 -1.8": ["participative"], "-6.0 23.3 0.2": ["absolutist"], "12.0 1.7 13.7": ["solarium"], "-1.5 3.3 6.6": ["elongation"], "-4.4 -3.6 5.8": ["arthroscopic"], "-0.8 15.9 2.8": ["forthrightness"], "7.5 7.9 32.6": ["garlicky"], "0.3 18.7 13.4": ["hoodlum"], "-0.6 18.4 6.3": ["objector"], "1.0 9.2 -1.6": ["meditated"], "5.9 16.0 11.0": ["unsolvable"], "-4.3 2.5 7.2": ["therefrom"], "12.7 26.0 13.6": ["commie"], "-2.1 1.4 7.6": ["engagingly"], "-4.4 5.3 8.2": ["yarders", "stickback"], "-2.1 4.5 7.8": ["sitdown"], "10.8 22.2 12.1": ["cudgel"], "9.2 8.0 -0.8": ["singe"], "12.5 13.1 11.4": ["stinkin"], "-5.3 2.6 0.1": ["bondsman"], "0.7 3.9 -3.4": ["activator"], "12.9 21.0 10.7": ["scrambler"], "3.7 16.1 12.3": ["deadpans"], "6.8 10.4 0.8": ["defacement"], "10.6 1.5 9.4": ["rom"], "-3.5 19.3 7.8": ["negativism"], "12.7 6.4 10.6": ["socking"], "5.4 7.6 -1.3": ["waterless"], "-0.8 8.6 8.7": ["kl"], "4.8 16.4 -1.1": ["monotheism"], "7.9 10.9 0.7": ["suss"], "-7.3 10.4 23.4": ["roux"], "30.1 9.8 15.3": ["phallic"], "2.9 6.2 6.5": ["requisites"], "-1.8 6.2 3.5": ["beseeched"], "1.1 5.6 3.4": ["contretemps"], "-3.5 12.7 5.7": ["shofar"], "10.8 1.9 10.9": ["busker"], "8.5 2.1 4.3": ["turndown"], "3.7 6.0 22.2": ["epicurean"], "20.3 8.5 5.5": ["hucksters"], "-2.5 9.0 8.2": ["ballclubs"], "-10.8 4.6 -1.3": ["neurosurgical"], "-2.0 8.3 10.2": ["fx"], "18.6 13.7 12.6": ["sundial"], "13.5 7.1 13.4": ["backslapping"], "8.3 6.7 7.2": ["undulations"], "8.5 10.2 7.0": ["col"], "-3.5 3.4 3.2": ["prostituted"], "17.3 4.1 -1.0": ["unbundle"], "-4.4 10.7 3.5": ["discourteous"], "-2.8 9.4 14.4": ["tillers"], "12.0 5.4 12.0": ["trainwreck"], "3.6 8.4 8.5": ["protease"], "12.2 8.7 6.9": ["perestroika"], "-1.3 7.9 15.8": ["camelina"], "1.3 15.3 5.4": ["forewarning"], "18.0 6.5 22.0": ["whitish"], "8.5 27.2 6.0": ["perfidy"], "4.7 11.0 7.6": ["furrows"], "5.6 31.2 4.6": ["repulse"], "17.0 2.5 4.7": ["glittered"], "-3.4 8.4 16.3": ["recurve"], "8.1 13.8 7.1": ["miser"], "-2.2 8.9 3.8": ["frivolously"], "10.7 1.3 6.4": ["fritz"], "2.9 -1.6 12.7": ["pero"], "1.5 10.2 6.1": ["clasps"], "5.7 7.8 3.1": ["squanders"], "-3.2 11.2 2.3": ["overemphasize"], "11.1 6.6 14.9": ["luxuriant"], "4.2 5.5 9.4": ["skivvies"], "9.1 12.7 9.5": ["bobbies"], "2.1 11.5 7.0": ["qubits"], "-0.4 1.7 11.2": ["casein"], "2.4 0.5 14.9": ["gastro", "linocuts"], "12.6 1.6 3.0": ["jangling"], "9.2 1.9 9.2": ["megastars"], "2.5 7.3 11.4": ["dumper"], "-5.9 12.6 2.7": ["requisitions"], "2.4 12.2 4.3": ["emoting"], "10.5 8.6 17.5": ["suntan"], "18.1 1.8 0.6": ["refashioned"], "-3.9 13.2 1.1": ["haranguing"], "9.5 3.7 12.7": ["blithe"], "10.8 5.0 10.8": ["michael"], "-2.2 -0.4 12.0": ["cyclocross"], "15.6 -3.8 5.3": ["een"], "2.9 5.2 6.3": ["entertainingly"], "4.2 8.5 13.4": ["thruster"], "14.5 4.4 15.7": ["paisley"], "-1.5 8.3 2.4": ["depositories"], "1.5 14.2 3.0": ["assiduous"], "-1.8 1.0 0.7": ["proofread"], "5.0 10.8 34.0": ["musky"], "13.2 14.3 11.1": ["thrones"], "2.5 -0.9 15.2": ["cobblers"], "4.3 21.1 9.9": ["iraq"], "14.9 10.9 14.1": ["avaricious"], "-6.3 -3.3 -4.8": ["practicum"], "9.8 13.7 13.7": ["grunted"], "0.2 5.4 13.5": ["abutment"], "8.4 20.5 8.2": ["pointlessly"], "-0.6 12.8 7.6": ["trendlines"], "6.0 2.6 36.2": ["chub"], "-1.7 4.7 1.0": ["fanzine"], "5.0 16.0 -1.6": ["assessee"], "2.8 8.9 3.3": ["northeastward"], "9.4 15.7 16.8": ["gorse"], "7.0 8.1 12.0": ["bobsledding"], "8.0 -2.9 -0.9": ["quashes"], "11.9 8.7 20.3": ["pachyderms"], "13.2 1.8 10.8": ["mamas"], "-1.6 29.0 6.1": ["humvee"], "11.8 6.0 15.3": ["cobble"], "1.3 3.9 -1.0": ["prejudged"], "4.2 12.3 5.2": ["cabled"], "-1.2 4.2 5.9": ["brakeman"], "6.0 4.2 30.3": ["tern"], "8.0 17.5 2.1": ["exalt"], "-4.6 4.5 0.7": ["submarkets"], "8.5 0.4 12.2": ["pinochle"], "3.3 3.7 12.5": ["spritz"], "2.3 13.5 7.6": ["distressingly"], "14.2 6.4 2.8": ["hooray"], "13.0 11.7 14.9": ["prizefighter"], "-7.8 -4.9 3.5": ["menstruating"], "2.1 9.9 16.3": ["distemper"], "-2.0 -1.0 2.5": ["polymorphisms"], "13.2 1.8 13.4": ["gazebos"], "0.4 8.4 17.3": ["libation"], "1.2 8.8 1.2": ["lambaste"], "10.9 6.2 9.2": ["vibrantly"], "-4.5 11.6 6.6": ["reenact"], "7.1 11.2 7.3": ["obsequious"], "-8.6 1.5 8.9": ["criminologists"], "-2.8 4.9 10.3": ["reinstitute"], "9.8 20.2 2.1": ["outflanked"], "-2.3 -1.1 12.3": ["fluoxetine"], "8.2 9.4 6.3": ["accosting"], "6.3 22.7 3.0": ["mendacious"], "0.6 7.9 4.2": ["modifiable"], "-11.6 3.5 -2.1": ["adduced"], "3.8 -0.5 11.6": ["surnamed"], "7.3 8.2 21.0": ["alfresco"], "13.6 25.2 11.3": ["expansionism"], "-0.8 -0.6 9.1": ["waisted"], "0.2 8.7 6.3": ["immunologist"], "5.2 13.2 23.6": ["rhododendron"], "0.2 8.0 -0.5": ["accelerations"], "4.8 13.6 11.7": ["mutuality"], "15.5 10.3 10.2": ["buzzsaw"], "-1.7 3.4 4.9": ["driveshaft"], "2.2 4.7 10.2": ["tokenism"], "0.2 3.1 6.9": ["skullcap"], "1.0 14.2 7.9": ["inhabitable"], "-0.6 2.5 5.0": ["limiter"], "-2.0 -0.4 0.2": ["hypotension"], "0.4 8.9 39.1": ["peppercorns"], "7.0 7.4 5.8": ["snoozer"], "-0.3 17.0 6.8": ["philosophic"], "-0.1 6.9 8.5": ["literati"], "9.8 2.6 7.3": ["ge"], "-1.8 25.6 6.2": ["dialectic"], "4.6 19.8 9.5": ["contrarians"], "3.8 -2.8 1.1": ["ation"], "-3.9 4.3 -0.3": ["overstaffed"], "18.2 3.8 6.8": ["hotshots"], "-1.5 9.7 6.7": ["propellants"], "5.1 7.2 5.9": ["pushchair"], "-3.3 6.2 8.6": ["eclecticism", "fluorouracil"], "-4.6 1.7 14.1": ["smallholders"], "22.1 6.0 13.1": ["incongruously"], "-11.4 0.9 5.6": ["corticosteroid"], "6.2 5.0 7.1": ["bordello"], "1.0 20.8 3.6": ["themself"], "2.4 5.8 2.9": ["auteurs"], "4.2 1.5 0.6": ["nondiscriminatory"], "3.5 10.9 9.4": ["histamine"], "8.2 16.5 5.1": ["cavalierly"], "7.3 19.5 3.0": ["wartorn"], "12.9 10.7 14.7": ["shamans"], "3.1 2.6 12.3": ["mulesing"], "-2.8 10.1 2.1": ["darkhorse"], "4.0 4.5 3.9": ["brio"], "11.6 -1.6 -0.4": ["centrestage"], "6.7 14.5 15.2": ["windless"], "7.2 9.2 9.0": ["projectionist"], "-0.6 10.3 18.8": ["birdwatching"], "-1.0 -1.4 2.0": ["securitize"], "10.7 14.8 15.6": ["hidebound"], "-0.3 0.8 12.2": ["ako"], "3.4 14.6 5.1": ["galleys"], "5.1 1.9 4.9": ["fretful"], "-0.0 -0.0 3.7": ["presbytery"], "-6.6 26.2 -4.1": ["delegitimize"], "-7.2 5.9 15.5": ["tannin"], "5.0 10.5 -2.0": ["ascribing"], "2.2 3.1 25.6": ["lemony"], "2.5 9.1 -1.2": ["untiring"], "-7.4 10.6 0.6": ["maltreated"], "1.6 8.6 11.2": ["sorafenib"], "-2.5 7.5 11.8": ["commissaries"], "8.5 12.6 2.0": ["rucksacks"], "-6.3 4.3 7.3": ["formularies"], "1.7 5.6 9.5": ["climatology"], "8.1 12.4 29.0": ["eggshell"], "6.3 4.0 8.3": ["modelers"], "-1.4 -3.0 20.7": ["salmonellosis"], "-7.6 4.0 1.2": ["pathophysiology"], "5.2 6.9 -3.5": ["valueless"], "0.5 8.2 2.2": ["exhuming"], "10.2 21.7 6.6": ["contemptuously"], "0.6 0.6 10.3": ["autologous"], "-5.1 8.3 5.3": ["wastefully"], "1.2 3.4 -0.5": ["hydrotherapy"], "3.7 6.7 5.7": ["salvages"], "11.3 7.0 8.7": ["crowbars"], "-12.0 5.3 4.1": ["hemostasis"], "-5.7 2.9 1.9": ["agronomic"], "8.2 1.0 12.9": ["overindulgence"], "8.3 7.8 6.9": ["jinking"], "13.5 8.9 12.7": ["jiffy"], "3.9 12.3 13.7": ["guffaw", "stooling"], "11.9 20.3 2.7": ["undisguised"], "13.2 -1.3 9.3": ["eyeglass"], "-9.4 6.4 5.0": ["cardmembers"], "1.2 5.8 1.8": ["ameliorated"], "2.6 4.5 -2.0": ["annexe"], "-4.2 1.3 24.2": ["chana"], "19.5 7.9 10.8": ["doorstop"], "2.1 17.7 11.2": ["daringly"], "6.5 18.5 19.5": ["microorganism"], "10.2 8.2 2.6": ["billow"], "4.7 10.2 -0.9": ["quenching"], "15.5 5.5 22.1": ["marzipan"], "1.1 9.8 -1.1": ["misplace"], "-4.6 10.2 0.9": ["teledensity"], "6.8 -10.3 -3.3": ["overbilled"], "-2.2 11.9 2.9": ["sensationalize"], "0.4 12.7 3.5": ["seceding"], "-1.8 27.6 13.8": ["questing"], "2.3 6.3 -0.5": ["flammability"], "2.9 14.1 3.8": ["overhears"], "3.3 18.9 8.3": ["senselessly"], "3.6 2.9 6.3": ["roadsters"], "8.2 8.9 20.6": ["fryers"], "5.6 2.3 9.7": ["reprieved"], "4.6 22.9 30.0": ["weevils"], "5.4 31.0 5.1": ["usurper"], "10.2 -4.2 12.8": ["pert"], "-5.6 5.6 6.2": ["seaters"], "-10.4 8.9 2.7": ["redactions"], "62.8 18.5 17.6": ["goliath"], "2.2 1.5 7.5": ["wrinkling"], "10.2 15.4 8.7": ["hahaha"], "0.4 7.9 0.3": ["tonality"], "0.7 12.0 12.6": ["bandhs"], "11.0 -1.1 9.7": ["nubile"], "-1.0 9.0 9.7": ["locket"], "2.3 16.6 5.3": ["besmirch"], "-2.6 -2.8 11.0": ["wt"], "14.9 2.2 13.7": ["voraciously"], "-2.8 1.9 12.6": ["sunbed"], "-5.3 5.5 0.0": ["individualize"], "4.4 13.9 8.6": ["mutuals"], "12.7 13.3 18.1": ["headhunting"], "-6.4 3.4 8.4": ["epidemiologic"], "16.8 7.6 12.2": ["arced"], "-7.1 5.9 -2.2": ["professionalize"], "10.8 4.6 6.0": ["sidled"], "0.5 4.8 5.3": ["pulps"], "8.3 8.8 18.0": ["shamrocks"], "0.7 20.2 4.0": ["courteously"], "-16.6 6.3 6.9": ["immunosuppression"], "-2.3 0.4 8.9": ["millwork"], "4.5 12.4 -2.4": ["serially"], "7.4 7.2 7.3": ["gigolo"], "-1.1 6.6 25.2": ["powerboats"], "-0.4 3.8 33.2": ["currants"], "-1.9 14.4 -0.2": ["resonances"], "11.7 12.2 6.0": ["blankly"], "7.1 4.9 -2.4": ["tarring"], "0.3 -4.9 7.3": ["playgroups"], "-6.6 3.9 2.2": ["expounds"], "6.6 14.9 12.5": ["equinox"], "6.3 6.3 7.4": ["whinging"], "15.3 13.8 8.5": ["yahoos"], "-0.1 15.5 8.9": ["baptize"], "13.2 11.8 2.6": ["lulling"], "7.1 12.8 43.0": ["lobsterman"], "2.4 3.4 4.9": ["lede"], "3.4 6.4 13.6": ["coarser"], "8.9 10.8 4.4": ["knoll"], "-2.0 21.1 7.0": ["kinsmen"], "-6.2 2.6 7.8": ["sunglass"], "13.3 1.7 9.7": ["puttering"], "8.2 2.2 7.2": ["rollin"], "2.4 7.0 10.7": ["imo"], "11.3 7.6 22.3": ["nonnative"], "13.9 14.3 6.2": ["magnetized"], "10.3 5.4 4.5": ["yakking"], "13.0 20.4 9.1": ["terrorizes"], "-1.1 12.3 12.8": ["hypoxic"], "4.7 13.8 26.2": ["ornamentals"], "5.4 9.1 6.7": ["scoutmaster"], "1.5 8.0 33.6": ["durian"], "20.2 5.6 15.9": ["waddling"], "15.8 12.3 9.7": ["cometh"], "16.3 16.0 11.1": ["swiftest"], "-7.8 9.8 6.3": ["wrestlebacks"], "10.7 12.7 7.1": ["hither"], "4.8 3.3 3.0": ["autonomic"], "3.0 6.3 5.1": ["chairlifts", "roomies"], "0.2 17.9 7.5": ["razzing"], "2.5 23.1 5.9": ["chivalrous"], "13.2 7.7 1.0": ["german"], "0.7 -0.3 1.2": ["nostalgically"], "-3.1 7.2 19.3": ["reseeding"], "4.7 0.5 8.7": ["quintuplets"], "-2.5 11.3 16.5": ["dialup"], "2.9 11.1 19.3": ["vocalizations"], "1.2 4.1 11.3": ["yong"], "-10.3 2.6 -1.7": ["indisposed"], "8.6 8.0 11.2": ["croak"], "17.3 2.5 13.9": ["bung"], "-10.1 0.2 4.9": ["stagings"], "-4.7 4.5 15.9": ["impoundments"], "4.8 -6.6 12.7": ["pedigreed"], "12.1 10.3 15.8": ["floaty"], "6.4 3.1 57.7": ["hake"], "7.4 16.3 0.7": ["extricating"], "0.8 8.3 38.1": ["fishmonger"], "-6.7 2.7 1.0": ["evidencing"], "5.8 5.9 13.9": ["follicle"], "3.0 4.5 10.8": ["reimportation"], "-3.6 14.4 -4.2": ["combustibles"], "12.1 5.5 4.7": ["reinstalling"], "-1.9 0.5 15.3": ["bangle"], "-15.2 9.7 23.8": ["jeera"], "7.8 0.8 2.4": ["prerelease"], "3.3 6.0 6.6": ["sullying"], "3.7 9.5 8.3": ["clearcut"], "1.6 13.0 31.9": ["milkweed"], "16.7 -3.1 6.4": ["carousels"], "8.4 8.0 4.2": ["muckraking"], "5.9 12.4 12.3": ["facetiously"], "-0.5 -11.2 3.2": ["preterm"], "-15.7 13.7 2.4": ["rabbinate"], "9.8 12.7 12.7": ["stultifying"], "14.3 6.1 9.5": ["lampshades"], "0.3 11.7 1.5": ["forger"], "2.8 3.0 -1.1": ["aftershave"], "4.2 6.2 3.7": ["backache"], "10.8 7.0 10.9": ["stargazers"], "10.5 24.5 16.7": ["brawlers"], "3.8 14.2 10.8": ["jujitsu"], "-5.7 3.3 10.5": ["digressions"], "-6.5 14.3 8.6": ["curtly"], "1.1 10.6 2.3": ["musters"], "-7.9 17.2 7.5": ["arrestee"], "5.4 2.2 -5.2": ["fitters"], "-2.6 7.7 45.0": ["kokanee"], "4.8 19.6 10.0": ["windstorms"], "3.2 14.4 6.3": ["paralytic"], "-5.5 10.1 -0.8": ["predisposes"], "4.0 -2.9 9.1": ["olefins"], "15.2 17.1 21.9": ["magpie"], "8.4 -1.8 3.6": ["obsesses"], "14.2 8.5 9.0": ["quickens"], "14.7 3.7 15.4": ["headpiece"], "13.5 3.9 6.5": ["sauntering"], "-2.2 10.1 5.4": ["churchgoer"], "10.0 2.8 29.8": ["birdseed"], "-7.4 9.9 6.1": ["supportable"], "1.7 7.1 51.5": ["croaker"], "1.9 9.6 11.1": ["thorax"], "-4.3 33.4 24.0": ["littoral"], "10.1 4.3 10.3": ["forgings"], "3.2 14.4 1.8": ["retrogressive"], "3.5 15.9 13.1": ["incomprehension"], "-1.2 15.7 13.3": ["gritters"], "9.9 1.3 9.9": ["mexico"], "4.5 4.5 10.0": ["coulda"], "-0.9 2.5 7.5": ["legalizes"], "15.6 8.9 16.3": ["mincing"], "5.9 6.1 17.6": ["jay"], "4.9 13.4 18.8": ["dawg"], "8.9 13.2 11.0": ["haram"], "-1.3 6.4 1.7": ["conceptualization"], "-1.5 6.3 9.4": ["alliteration"], "1.0 19.7 4.2": ["misdeed"], "10.1 -1.7 16.4": ["microwaved"], "0.5 6.8 -2.5": ["honourary"], "-0.9 4.6 5.5": ["boxscore"], "9.6 9.8 38.8": ["zooplankton"], "8.8 4.1 14.0": ["augers"], "15.4 6.6 32.2": ["tiki"], "3.6 13.7 12.4": ["niceness"], "9.5 0.4 11.0": ["lycra"], "13.0 2.9 6.2": ["micropayments"], "-0.0 9.4 7.1": ["retells"], "7.2 0.6 2.8": ["underpayments"], "12.6 8.8 0.3": ["reawaken"], "0.9 4.2 12.3": ["humus"], "12.0 3.3 10.4": ["grande"], "-2.7 12.2 3.1": ["phraseology"], "16.1 3.8 7.4": ["telescoping"], "-1.2 5.9 6.1": ["handphone"], "9.4 3.6 8.3": ["pricking"], "11.8 30.5 5.2": ["tyrannies"], "1.5 6.4 5.8": ["tenanted"], "3.7 -5.6 11.2": ["ning"], "5.0 -7.3 10.6": ["mohair"], "-3.0 5.0 9.8": ["matchmakers"], "-4.8 7.0 -4.6": ["unconverted"], "9.4 15.8 7.6": ["grovel"], "22.2 17.3 19.0": ["cannibalistic"], "4.3 12.9 12.3": ["intimations"], "0.7 8.3 8.6": ["precancerous"], "3.4 7.5 1.3": ["chowk"], "6.7 8.5 11.6": ["compacting"], "5.2 12.5 0.9": ["inestimable"], "-4.9 2.3 5.4": ["looseness"], "-1.9 31.2 6.4": ["naxals"], "-0.3 12.0 2.2": ["outliving"], "8.7 5.4 14.3": ["barstool"], "1.7 9.8 5.8": ["juxtapositions"], "1.5 -0.1 4.8": ["homages"], "-6.3 -2.1 13.8": ["postmenopausal"], "2.4 5.2 2.0": ["catchup"], "8.9 6.5 10.3": ["overconsumption"], "15.6 5.6 24.5": ["barbie"], "2.0 7.4 17.5": ["craic"], "-5.3 16.0 5.3": ["xv"], "3.4 7.9 9.6": ["facedown", "tracheobronchial"], "6.2 3.2 26.9": ["quesadilla"], "-2.0 5.8 0.3": ["chastises", "derostered"], "4.2 10.1 23.7": ["brackish"], "6.6 7.5 6.5": ["oversaturated"], "1.8 22.9 10.7": ["fierceness"], "16.2 4.3 9.4": ["shinier"], "0.1 7.0 2.9": ["empathizes"], "4.7 2.8 1.7": ["nonessentials"], "6.2 4.5 1.5": ["switchable"], "4.9 10.5 1.2": ["ambidextrous"], "22.2 5.2 17.3": ["tinfoil"], "0.7 2.8 19.4": ["cobs"], "5.7 -0.3 6.3": ["steepening"], "6.5 11.9 7.7": ["deports"], "27.0 8.9 35.0": ["gelatinous"], "1.2 12.7 7.9": ["ionosphere"], "5.1 16.5 1.1": ["telepathy"], "14.9 -6.4 9.5": ["pricy"], "12.2 7.7 12.6": ["steadies"], "10.6 2.3 10.1": ["baulk"], "-2.2 2.9 6.7": ["liturgies"], "-10.2 12.2 15.4": ["embarkation"], "3.1 9.7 13.9": ["brushy"], "15.4 27.2 2.3": ["onslaughts"], "23.4 12.8 37.9": ["octopuses"], "3.5 12.5 14.1": ["skank"], "6.0 -3.1 6.0": ["dragsters"], "11.5 2.7 11.8": ["bagful"], "-4.9 4.5 1.1": ["dispositive"], "0.7 -1.1 10.7": ["sibutramine"], "-4.8 11.0 1.1": ["innuendoes"], "21.8 20.8 23.4": ["serpents"], "4.3 14.5 8.7": ["cocksure"], "7.9 3.2 4.8": ["plumping"], "6.6 5.3 14.8": ["sandblasting"], "6.4 2.7 6.5": ["microelectronic"], "10.0 1.3 4.2": ["lazing"], "2.9 3.6 3.7": ["malformations"], "3.5 5.5 3.4": ["fluorine"], "11.9 4.7 11.7": ["dumpy"], "9.1 15.8 13.0": ["candlestick"], "6.2 25.3 1.5": ["machineguns"], "1.9 4.3 12.1": ["briquettes"], "9.9 0.3 15.7": ["flatlined"], "0.2 -1.9 7.9": ["reprieves"], "-1.4 3.5 7.0": ["opportunites"], "11.6 3.9 9.7": ["agglomeration"], "2.1 6.3 21.4": ["gi"], "10.4 6.7 -3.6": ["airless"], "26.8 5.1 1.2": ["demerge"], "10.4 15.1 1.2": ["braintrust"], "13.8 23.9 15.8": ["unfeeling"], "3.0 8.6 6.9": ["bobbles"], "8.4 3.7 30.5": ["tableside"], "14.4 17.5 9.7": ["obnoxiously"], "-10.6 11.7 3.9": ["prejudging"], "-0.7 2.0 6.2": ["sportscasters"], "8.0 1.6 7.5": ["trills"], "-0.4 11.5 -2.6": ["dilate"], "4.8 3.2 21.9": ["moe"], "-3.2 17.3 -1.9": ["denigrates"], "-1.2 7.4 -2.8": ["disabuse"], "9.5 15.9 7.1": ["trojans"], "1.7 9.9 1.2": ["pressurization"], "1.5 14.3 -4.9": ["comprehended"], "8.9 21.5 -2.3": ["ultranationalists"], "-2.4 -2.4 8.1": ["alopecia"], "3.6 1.8 8.6": ["chang"], "28.9 -2.4 -0.1": ["jv"], "-1.3 4.6 -1.7": ["solicitous"], "23.1 12.5 4.8": ["deliverer"], "8.1 6.1 15.2": ["coring"], "-2.8 5.6 3.7": ["indentified"], "4.2 -1.1 -0.0": ["kuna"], "6.8 6.3 14.0": ["clownish"], "15.6 -2.2 28.3": ["harborside"], "9.3 19.8 -2.1": ["doubter"], "-0.6 9.0 6.1": ["wether"], "1.6 11.3 8.9": ["deflator"], "5.9 10.4 19.3": ["parkers"], "-0.1 8.6 8.1": ["deadwood"], "5.1 -0.1 37.0": ["edamame"], "3.0 8.3 4.5": ["blurting"], "-0.3 9.3 3.2": ["particularity"], "11.4 4.3 14.8": ["pointman"], "-4.2 8.3 0.5": ["ameliorating"], "9.3 16.9 1.1": ["everyones"], "8.5 1.4 14.4": ["opal"], "3.8 7.2 45.3": ["seagrass"], "15.0 -2.6 4.1": ["marquis"], "17.5 -0.5 -5.0": ["spokesmodel"], "4.2 7.3 13.9": ["sam"], "9.6 5.5 3.9": ["synching"], "1.0 4.8 9.5": ["aur"], "10.3 7.1 7.3": ["pirouettes"], "7.3 4.4 0.8": ["minster"], "3.9 6.3 1.6": ["bade"], "13.2 13.0 9.6": ["mediaeval"], "18.7 2.8 7.5": ["gleamed"], "13.8 7.0 15.4": ["candelabra"], "-1.6 6.5 9.0": ["trumpeters"], "14.9 9.8 8.9": ["savanna"], "-0.8 11.7 1.5": ["pluralist"], "-3.7 2.7 5.1": ["atelier"], "-1.7 1.3 11.3": ["choppiness"], "20.1 4.4 7.2": ["boffo"], "4.6 4.3 15.7": ["methylmercury"], "-0.6 -0.5 19.3": ["wintered"], "6.4 5.1 11.0": ["yah"], "-7.1 4.0 4.8": ["cyclophosphamide"], "-7.3 -0.2 16.9": ["homebuying"], "7.0 8.1 0.7": ["astrophysicists"], "-0.8 11.8 9.4": ["stratigraphy"], "-4.1 0.1 5.0": ["luminaires"], "-2.7 4.3 6.9": ["enjoyably"], "10.2 5.7 2.6": ["beseeching"], "21.3 1.4 17.5": ["bungee"], "14.5 18.2 2.6": ["repellant"], "4.5 4.4 6.9": ["actin"], "4.6 4.3 14.6": ["cytoplasm"], "0.9 1.3 -1.1": ["upbraided"], "-0.7 2.0 1.7": ["earnt"], "7.0 13.2 13.0": ["lowlife"], "0.7 18.6 8.8": ["ballhandler"], "6.0 5.7 9.2": ["backhanding"], "7.9 13.1 -1.9": ["autobahn"], "9.4 1.0 4.4": ["coexisted"], "5.8 5.2 18.7": ["mojitos"], "7.1 13.7 16.5": ["deadweight"], "-7.9 -1.2 -1.0": ["matriculated"], "12.4 -6.4 3.6": ["wending"], "1.4 3.7 10.1": ["acreages"], "13.4 11.5 3.6": ["underperformers"], "0.1 2.5 8.1": ["bootcamp"], "0.6 9.8 9.4": ["lode"], "14.8 11.3 0.9": ["slickest"], "13.1 21.4 6.3": ["uncountable"], "-8.4 1.2 9.4": ["preconstruction"], "-0.2 6.3 11.1": ["oeuvres"], "-3.3 8.5 -2.4": ["exonerates"], "4.4 3.7 17.7": ["papyrus"], "-1.1 3.3 5.4": ["outturn"], "4.0 6.0 5.6": ["unfulfilling"], "10.4 7.9 5.9": ["hoofing"], "11.0 1.8 12.3": ["taffeta"], "2.6 9.0 -2.4": ["outranked"], "16.0 3.4 26.4": ["lemur"], "18.9 7.0 9.0": ["unfurls"], "12.5 4.7 4.7": ["swilling"], "4.4 -2.6 13.3": ["zippered"], "10.2 10.1 1.3": ["positing"], "5.5 12.5 6.7": ["grosser"], "1.3 16.6 2.2": ["upgradable"], "4.7 19.8 7.2": ["outfought"], "-0.4 16.6 5.2": ["affectation"], "3.8 11.5 7.2": ["straightforwardly"], "16.0 16.5 8.1": ["megalomania"], "1.6 10.7 10.0": ["amiably"], "14.9 8.3 10.2": ["thrashes"], "17.8 21.2 16.2": ["ghoul"], "13.8 20.0 7.4": ["storehouses"], "13.6 12.6 12.0": ["workmate"], "-2.9 9.7 12.3": ["unders"], "-10.6 8.5 -4.9": ["misinterpretations"], "15.6 22.0 11.7": ["demigod"], "16.5 4.8 4.7": ["ized"], "7.5 8.8 10.9": ["fey"], "9.9 10.3 13.0": ["scareware"], "7.8 15.7 13.3": ["unrequited"], "-4.8 12.7 2.1": ["acclimating"], "-3.7 10.6 8.5": ["stalemates"], "14.8 15.3 1.0": ["searchlight"], "-7.7 11.0 13.7": ["allocable"], "2.7 11.3 8.3": ["goddaughter"], "-1.7 16.4 11.1": ["unluckily"], "2.6 1.0 9.9": ["overdid"], "13.2 6.4 12.6": ["tinkling"], "6.0 10.9 13.6": ["wittily"], "7.0 7.4 14.6": ["downers"], "0.8 3.2 2.1": ["sportswoman"], "-8.1 2.8 7.6": ["birthrates"], "7.4 3.3 5.1": ["satirized"], "-6.8 2.6 -3.0": ["hydrocephalus"], "12.5 1.5 6.6": ["acetylene"], "5.4 1.2 10.9": ["bootstrap"], "3.4 6.0 12.3": ["fn"], "8.7 2.7 2.4": ["subsectors"], "11.7 18.7 10.6": ["schemers"], "0.7 -2.5 8.8": ["longish"], "-1.0 18.4 6.5": ["outworking"], "12.9 2.3 2.1": ["skr"], "-0.0 5.4 14.9": ["mausoleums"], "5.5 13.1 7.6": ["cluelessness"], "9.3 10.7 11.7": ["unhooked"], "-4.7 10.5 14.8": ["goldsmith"], "-1.7 10.2 2.1": ["ruminate"], "4.6 2.9 5.0": ["cultish"], "10.7 8.4 8.9": ["homeward"], "10.9 -0.9 6.5": ["ekes"], "2.3 7.6 3.9": ["satires"], "-6.5 12.5 -1.9": ["parroted"], "5.2 21.4 8.4": ["sophistry"], "-4.3 1.9 7.2": ["drawstrings"], "-6.7 14.6 6.2": ["ecclesial"], "14.9 8.0 12.4": ["dildo"], "9.9 0.4 5.5": ["unceremonious"], "1.0 -1.5 9.7": ["illus"], "13.5 15.2 10.2": ["schmuck"], "5.5 5.1 14.7": ["rhymed"], "9.7 2.9 8.0": ["skyboxes"], "10.7 8.8 5.4": ["bookselling"], "-3.6 8.8 17.1": ["scleroderma"], "-0.9 7.2 8.7": ["footloose"], "0.4 14.8 8.7": ["northerner"], "-7.4 -2.9 -4.8": ["monographs"], "4.6 6.4 19.6": ["cornice"], "7.2 9.3 3.4": ["disdains"], "-5.5 10.5 15.7": ["overstock"], "15.7 13.6 23.8": ["fanny"], "5.7 8.0 10.2": ["lisp"], "14.0 20.2 6.6": ["plutocracy"], "4.7 -1.0 -0.6": ["medicals"], "6.3 7.6 -6.5": ["etquot"], "-5.8 8.6 5.3": ["picoplatin"], "-0.5 5.3 6.4": ["chairmanships"], "7.8 13.5 12.7": ["quot"], "7.0 -0.1 7.4": ["smutty"], "-3.6 7.6 4.8": ["codification"], "6.0 3.9 16.2": ["batboy"], "-5.4 0.7 -3.7": ["administrated"], "11.6 6.0 11.8": ["hairpiece"], "14.2 8.6 11.7": ["lampshade"], "-4.0 26.1 6.4": ["infiltrations"], "10.0 2.3 14.6": ["yikes"], "-7.3 1.6 2.0": ["bylines"], "20.2 2.7 20.9": ["ballyhoo"], "3.5 3.4 10.1": ["farmhands"], "3.9 -1.5 13.1": ["florida"], "15.5 7.7 20.4": ["dappled"], "-2.4 8.7 7.9": ["longwall"], "5.3 4.7 3.5": ["polyclinics"], "8.5 24.5 23.7": ["borer"], "-2.2 4.5 8.3": ["oxygenation"], "7.0 16.0 6.8": ["generative"], "2.9 10.4 15.4": ["folkie"], "-2.7 11.9 21.6": ["spiciness"], "6.4 3.7 8.3": ["hos"], "-1.1 6.2 15.5": ["bachelorette"], "-1.5 17.4 -1.0": ["discomforts"], "3.2 6.3 5.1": ["synergistically"], "6.8 9.9 15.2": ["betcha"], "-2.2 2.3 2.1": ["reinsert"], "1.0 5.6 9.9": ["pronunciations"], "-1.4 6.6 5.9": ["impingement"], "7.1 -1.6 14.9": ["hwa"], "0.1 11.0 -4.5": ["eulogizing"], "9.5 3.4 12.0": ["hermaphrodite"], "-3.0 1.9 -8.4": ["echocardiography"], "-3.9 0.6 9.3": ["brewmaster"], "5.3 6.7 1.3": ["credulity"], "6.3 17.5 4.8": ["diktats"], "1.4 4.7 9.7": ["subcompacts"], "9.3 16.4 14.3": ["mythologies"], "8.6 15.7 5.6": ["instabilities"], "4.7 4.0 11.3": ["guttering"], "5.7 4.0 6.5": ["dreck"], "19.4 1.5 16.9": ["lollies"], "-2.0 14.0 18.1": ["yeasts"], "1.2 -1.7 8.4": ["barium"], "1.5 8.3 7.3": ["circadian"], "3.1 -0.3 18.4": ["potlucks"], "-2.3 2.5 -1.6": ["enoxaparin"], "1.4 6.3 11.3": ["curtsy"], "8.2 -0.2 5.2": ["greases"], "13.6 8.9 1.6": ["immortalize"], "-4.6 4.9 16.4": ["bloodstock"], "9.5 9.3 -1.6": ["autoworker"], "-7.3 4.0 2.0": ["gastroenterologists"], "-9.4 9.4 -1.8": ["recanting"], "5.1 5.2 8.3": ["motherless"], "9.7 1.0 11.6": ["graphing"], "-5.8 11.0 0.4": ["conflated"], "6.6 16.1 10.2": ["nothings"], "6.9 12.4 9.1": ["starves"], "8.7 9.8 0.1": ["acing"], "-1.2 16.1 1.1": ["rousted"], "-0.2 7.8 -3.7": ["dissociation"], "5.5 -5.7 9.8": ["minidress"], "7.6 5.2 27.0": ["brioche"], "4.6 1.2 -0.1": ["ensuite"], "4.3 15.7 15.0": ["leeward"], "-0.5 19.8 12.9": ["intraparty"], "2.5 27.7 10.3": ["turncoats"], "-6.4 2.0 7.4": ["ordinations"], "18.0 4.8 0.3": ["megabucks"], "5.4 20.9 14.8": ["badness"], "2.4 13.2 8.9": ["divisible"], "0.8 14.7 8.6": ["imperfectly"], "6.7 7.0 54.2": ["monkfish"], "25.3 9.1 15.5": ["pygmy"], "3.2 18.0 8.3": ["belittles"], "-3.7 2.6 1.7": ["modulates"], "0.2 4.6 -0.1": ["proctor"], "8.1 8.7 11.4": ["hominids"], "2.5 7.2 -0.2": ["underplay"], "8.9 7.0 6.4": ["lederhosen"], "6.3 3.0 4.4": ["doff"], "10.5 16.4 8.2": ["chattel"], "-1.0 16.9 2.3": ["unsupportive"], "-3.3 6.1 7.9": ["penitentiaries"], "-8.7 6.6 7.7": ["redshirts"], "-2.7 20.3 5.6": ["inactivate"], "5.6 14.0 12.0": ["pugilistic"], "14.7 12.2 -0.6": ["ostentatiously"], "6.7 6.8 8.6": ["dongles"], "9.6 -0.1 8.4": ["freighted"], "-1.2 15.7 14.0": ["dozer"], "3.8 8.5 -1.4": ["untarnished"], "2.2 -1.2 0.8": ["upscaling"], "7.4 6.6 17.2": ["clinking"], "8.4 -2.8 16.2": ["mislabeling"], "3.2 6.4 16.4": ["drillship"], "-2.8 15.6 19.2": ["seamanship"], "15.1 7.6 10.4": ["scrabbling"], "-14.3 9.4 4.2": ["levodopa"], "-0.6 16.0 6.7": ["undiplomatic"], "18.7 15.7 8.8": ["interlocked"], "5.9 19.7 37.1": ["hydrilla"], "0.7 13.3 5.8": ["lusts"], "-1.7 -0.3 4.2": ["toothpastes"], "-8.1 10.2 5.0": ["defrag"], "-3.1 16.7 3.9": ["schisms"], "8.7 7.5 10.4": ["dewy"], "-3.4 7.6 14.0": ["genera"], "5.1 6.3 4.6": ["effervescence"], "3.0 20.1 4.5": ["helicoptered"], "6.9 -1.5 28.3": ["calico"], "6.5 11.2 14.1": ["footrace"], "11.8 4.5 8.8": ["conga"], "2.9 4.6 -0.6": ["uplifts"], "1.9 -0.2 11.7": ["drams"], "5.0 5.9 6.7": ["wracking"], "-9.1 2.4 9.0": ["atta"], "-3.1 4.6 7.3": ["unfussy"], "-7.6 3.8 7.8": ["premarital"], "10.7 2.4 2.9": ["lampoons"], "3.0 20.4 15.6": ["frightfully"], "-11.0 10.2 20.2": ["vermouth"], "2.4 13.0 2.3": ["newsreels"], "-2.1 8.1 -1.2": ["transited"], "6.7 8.5 3.3": ["parsimonious"], "11.9 6.6 24.0": ["popsicles"], "0.4 6.4 3.6": ["acclimatised"], "-8.6 11.4 1.1": ["airworthy"], "0.2 8.8 1.8": ["enjoining"], "10.8 16.4 27.3": ["seascape"], "7.1 14.4 0.2": ["coconspirators"], "3.7 12.3 23.9": ["clematis"], "-2.8 -4.6 5.3": ["reclassifications"], "-8.2 -2.1 0.7": ["mediations"], "2.8 13.7 7.2": ["clench"], "3.1 2.5 -1.6": ["febrile"], "5.3 6.8 4.9": ["fumigated"], "11.2 2.7 8.0": ["blowups"], "-1.8 14.6 6.5": ["inheritors"], "-1.7 10.9 -6.9": ["infers"], "-11.8 14.7 5.9": ["chloroquine"], "-5.3 11.2 -0.6": ["ionization"], "4.1 8.8 4.2": ["homeostasis"], "-5.0 4.6 9.6": ["hernias"], "3.3 2.8 7.3": ["broadsheets"], "0.7 2.0 10.6": ["anthracite"], "-8.0 8.8 8.3": ["lamivudine"], "4.4 10.7 21.4": ["waitstaff"], "-0.3 24.3 3.3": ["homophobe"], "7.9 12.8 3.4": ["protectively"], "4.7 5.8 7.7": ["profs"], "-0.6 5.6 5.0": ["presspersons"], "4.9 5.0 38.4": ["teriyaki"], "5.7 4.4 27.7": ["poutine"], "4.8 5.6 5.0": ["playin"], "3.7 16.2 11.8": ["replenishes"], "3.3 10.2 16.2": ["teahouse"], "5.8 11.2 8.3": ["lamely"], "-4.0 4.5 2.9": ["quarterfinalists"], "-0.4 11.1 6.7": ["asst"], "0.1 4.1 5.8": ["piques"], "7.2 11.3 11.0": ["aunty"], "16.7 14.0 16.6": ["simian"], "0.6 3.1 15.8": ["moly"], "4.7 -2.6 2.9": ["harkening"], "-6.1 11.3 3.5": ["mistrustful"], "2.4 11.0 5.4": ["unsullied"], "2.1 5.2 -1.1": ["authenticates"], "8.8 6.6 7.9": ["unseasonable"], "22.1 13.8 15.1": ["skittering"], "25.9 27.7 27.7": ["goblin"], "2.1 11.7 4.1": ["denier"], "14.6 11.7 14.2": ["rollup"], "-7.5 5.3 6.6": ["headedness"], "5.6 4.4 9.7": ["tinkers"], "-5.9 0.8 2.1": ["rechecked"], "4.2 13.5 13.5": ["quarrelsome"], "-0.8 18.4 2.9": ["individualist"], "-4.0 14.4 -0.1": ["vendettas"], "11.9 6.4 0.3": ["satirizing"], "7.9 6.3 0.5": ["anodyne"], "4.0 2.0 11.5": ["unevenness"], "5.0 5.3 8.7": ["couturier"], "15.4 9.3 13.2": ["wiggles"], "7.4 0.9 9.2": ["sequencer"], "13.1 17.0 16.1": ["dodgers"], "6.2 -1.3 20.1": ["moi"], "-6.9 2.3 -1.5": ["drivability"], "11.9 14.4 8.4": ["lamest"], "6.5 2.1 3.5": ["railyard"], "1.1 14.6 7.4": ["humanists"], "4.1 13.0 2.6": ["providential"], "4.7 17.7 11.9": ["privateers"], "-0.9 -0.5 11.9": ["cabarets"], "-4.3 16.8 4.4": ["elope"], "8.4 4.4 14.8": ["superpipe"], "11.6 14.5 17.3": ["shrew"], "7.4 7.5 7.9": ["crescendos"], "1.1 25.7 3.6": ["dehumanization"], "-1.3 9.9 15.2": ["amoxicillin"], "9.5 4.0 9.4": ["windowed"], "6.7 0.7 4.1": ["switcheroo"], "15.1 12.6 15.1": ["throwdown"], "7.2 2.6 13.4": ["shellacked"], "-0.4 16.7 5.3": ["nonthreatening"], "8.2 10.9 2.2": ["papering"], "5.4 3.0 9.4": ["emulsions"], "-13.1 5.1 1.5": ["hematologic"], "1.0 37.5 6.4": ["belligerents"], "-6.2 10.7 3.5": ["endears"], "6.7 5.3 25.9": ["scone"], "-10.2 6.4 14.2": ["antimicrobials"], "5.6 25.9 11.0": ["retaliates"], "10.6 4.9 0.4": ["megahit"], "2.4 5.3 0.6": ["disallows"], "13.2 7.8 8.6": ["vertiginous"], "28.4 9.6 11.6": ["wiz"], "7.7 -2.1 2.3": ["ast"], "13.2 -3.6 17.5": ["untangled"], "10.1 -1.3 -1.5": ["als"], "16.3 1.9 1.3": ["photocopiers"], "9.5 13.8 11.4": ["cleave"], "17.0 3.7 25.3": ["boa"], "-2.1 11.4 14.7": ["harriers"], "3.9 4.2 22.2": ["stevedoring"], "1.1 8.6 9.1": ["hain"], "5.3 8.7 16.8": ["cookin"], "15.1 20.8 10.2": ["infesting"], "6.5 5.7 32.6": ["aioli"], "2.4 13.1 7.6": ["ratted"], "-0.7 2.6 3.0": ["dissolute"], "2.6 -2.1 7.6": ["vermiculite"], "11.6 19.5 9.7": ["evermore"], "6.7 12.3 6.5": ["workaholics"], "7.5 8.0 15.2": ["seaming"], "-8.4 18.3 12.5": ["intoxicant"], "-6.2 6.3 21.6": ["snowbird"], "12.3 5.7 11.8": ["frolics"], "3.6 19.9 9.0": ["sunup"], "-0.6 7.9 -0.6": ["assented"], "8.9 0.1 -1.3": ["fawned"], "1.3 16.9 8.7": ["hardheaded"], "-8.5 1.4 -5.3": ["percutaneous"], "13.3 11.9 6.4": ["suggestively"], "-6.0 6.2 9.7": ["rebooking"], "6.0 6.7 6.0": ["je"], "5.7 0.4 1.0": ["acn"], "11.6 14.3 8.9": ["turbaned"], "5.2 11.6 9.5": ["resenting"], "-2.4 3.3 14.8": ["beachwear"], "3.4 8.1 30.6": ["cannoli"], "-7.6 4.5 1.2": ["topiramate"], "-1.2 10.2 9.1": ["venerate"], "1.2 11.2 6.9": ["alprazolam"], "10.1 8.7 12.0": ["fluffing"], "-6.6 2.1 10.9": ["therms"], "4.4 9.0 6.9": ["toto", "sobfest"], "4.4 7.0 8.1": ["embossing"], "9.0 14.8 12.3": ["dukes"], "4.4 8.6 -2.1": ["responsiblity"], "2.7 5.6 28.0": ["naan"], "5.5 14.6 6.7": ["eunuch"], "4.0 5.4 8.1": ["moisten"], "1.4 10.0 -2.4": ["illegitimately"], "2.0 14.1 7.9": ["muzzles"], "-3.0 8.5 1.7": ["becasue"], "15.5 7.3 10.2": ["quaintly"], "0.6 0.9 -1.5": ["sonography"], "9.0 7.0 6.1": ["mineworkers"], "19.2 16.5 0.6": ["zaps"], "2.2 4.8 2.5": ["nazim"], "5.5 0.3 -2.4": ["advertorial"], "2.0 10.3 11.9": ["microtubules"], "4.6 0.1 4.6": ["dehumidifiers"], "-9.0 4.4 6.1": ["spillovers"], "22.9 13.4 9.9": ["automaking"], "6.3 3.0 4.2": ["illuminations"], "22.5 4.0 11.5": ["scrapers"], "12.2 8.0 17.2": ["trellises"], "-7.6 3.2 -12.0": ["affiliating"], "5.9 -2.7 2.3": ["litas"], "13.6 2.9 8.4": ["paintbrushes"], "15.1 4.5 9.3": ["sorter"], "-7.7 2.6 -4.2": ["analgesia"], "18.1 4.3 7.8": ["trundle"], "4.3 2.8 49.3": ["beluga"], "7.8 2.4 5.1": ["kickin"], "7.9 9.2 1.6": ["breezily"], "11.7 9.3 9.3": ["sudoku"], "0.7 18.7 12.4": ["bromance"], "0.0 4.9 3.8": ["neurodegeneration"], "-1.5 19.6 6.2": ["intentioned"], "11.9 12.8 7.9": ["insomniac"], "-3.9 17.2 13.9": ["wildlands"], "2.0 2.9 2.2": ["circulators"], "0.9 1.0 11.0": ["commingling"], "-0.4 6.0 5.8": ["reprice"], "18.3 7.2 22.2": ["gossamer"], "21.7 5.5 4.1": ["trundling"], "9.8 5.7 3.1": ["serenades"], "2.3 13.9 3.8": ["repetitively"], "7.7 -2.2 14.0": ["kimonos"], "8.3 8.8 12.9": ["turpentine"], "3.8 16.8 16.9": ["corvette"], "10.7 27.9 4.7": ["insidiously"], "10.4 6.2 10.8": ["questionably"], "9.5 1.7 11.7": ["chromed"], "-1.7 9.6 15.4": ["towpath"], "5.6 13.9 4.8": ["internees"], "11.4 4.6 10.3": ["seers"], "4.1 5.4 11.3": ["banister"], "1.9 8.6 35.3": ["bisque"], "8.0 4.4 13.4": ["tampon"], "14.4 9.0 12.3": ["cojones"], "9.5 10.8 11.2": ["abseiling"], "8.1 -0.5 10.1": ["tal"], "-3.1 3.1 5.8": ["caretaking"], "10.0 15.9 7.7": ["humbug"], "-0.5 2.8 12.3": ["seo"], "19.2 0.5 11.6": ["skittered"], "10.7 10.4 0.2": ["unexploited"], "18.8 3.0 7.6": ["teat"], "17.9 4.1 6.7": ["compo"], "1.2 17.2 1.5": ["understrength"], "0.7 12.1 5.1": ["tdahlberg"], "-5.0 16.6 11.7": ["sycophancy"], "10.6 -0.9 7.2": ["manifolds"], "14.5 -2.3 14.8": ["wooly"], "12.2 19.4 7.5": ["dumbass"], "1.9 7.5 5.1": ["dinked"], "-0.2 -1.0 4.2": ["multiplexed"], "11.5 8.1 7.5": ["waxwork"], "7.9 2.9 9.0": ["thermally"], "9.2 0.0 2.8": ["buzzy"], "17.7 3.8 2.3": ["oilmen"], "7.8 7.2 20.1": ["planking"], "7.7 7.6 6.2": ["bundlers"], "2.6 3.2 16.3": ["fedoras"], "3.3 14.0 1.0": ["agains"], "10.2 13.7 0.5": ["quasar"], "6.8 4.3 15.5": ["muslin"], "-5.1 8.1 -0.3": ["occassions"], "2.3 1.9 7.3": ["dargah"], "6.4 10.1 15.3": ["gon"], "-8.5 2.2 11.4": ["slouchy"], "15.7 10.6 -0.4": ["cheapness"], "2.4 19.9 14.8": ["insolence"], "-13.0 12.0 2.4": ["transfused"], "5.8 21.0 1.8": ["patsies"], "-6.5 3.3 13.0": ["charterers"], "-5.3 17.5 8.2": ["impassible"], "10.2 10.2 21.7": ["wisteria"], "-0.8 8.0 11.7": ["handpick"], "-2.2 6.8 -0.5": ["challan"], "15.5 6.6 1.6": ["jailbird"], "5.6 1.7 9.0": ["semipro"], "6.7 1.4 -2.3": ["relegates"], "9.8 15.6 22.2": ["armadillos"], "4.9 3.7 11.8": ["bassline"], "6.1 8.2 2.5": ["synched"], "-0.5 0.0 5.2": ["glycol"], "-0.2 8.9 -2.7": ["disavowing"], "17.0 6.6 2.3": ["conked"], "3.5 5.8 14.3": ["aunties"], "-1.2 6.6 6.1": ["drillholes"], "-0.1 16.0 12.7": ["maxims"], "5.4 0.4 7.7": ["diffusers"], "3.2 5.2 13.3": ["medleys"], "11.7 11.5 5.4": ["preposterously"], "6.7 1.3 2.8": ["reuses"], "4.9 26.2 10.4": ["sieges"], "-7.3 6.8 14.9": ["rescissions"], "9.2 17.0 6.6": ["permutation"], "-10.5 -6.6 0.2": ["heartwire"], "16.6 11.0 14.5": ["moats"], "14.2 14.3 7.3": ["pricks"], "5.6 7.0 29.6": ["persimmon"], "1.2 5.6 10.6": ["dependably"], "13.4 8.5 6.7": ["rainmaker"], "3.4 6.7 -6.1": ["trivializes"], "1.1 2.1 7.9": ["xpedx"], "2.1 -1.3 15.5": ["youngish"], "0.3 9.2 14.4": ["enthusiasms"], "-3.4 6.6 5.2": ["prefects"], "8.0 30.5 9.9": ["starship"], "1.5 12.7 13.1": ["pollinating"], "3.9 5.5 6.6": ["commerciality"], "5.5 9.7 11.1": ["flits"], "-3.4 14.1 -6.1": ["incriminated"], "-1.3 0.0 4.9": ["avant"], "-0.5 14.2 5.5": ["interpolation"], "2.4 5.7 4.4": ["broody"], "1.7 10.5 8.5": ["sunspot"], "-6.1 0.5 8.2": ["extracurriculars"], "14.1 10.8 16.5": ["hungrily"], "7.7 11.6 8.2": ["sociability"], "-3.4 3.9 -0.2": ["retitled"], "0.9 7.9 4.2": ["engrave"], "6.8 0.0 -1.9": ["traipsed"], "5.3 3.4 3.7": ["nb"], "10.4 12.0 10.7": ["gameshow"], "11.9 0.5 5.8": ["schlepping"], "12.4 -3.7 10.2": ["che"], "3.4 8.3 -2.4": ["befit"], "6.8 9.5 10.3": ["barefooted"], "6.7 6.6 8.6": ["diming"], "14.3 -2.4 6.5": ["teemed"], "13.6 19.7 10.7": ["godlike"], "7.0 7.6 19.0": ["pow"], "-0.3 8.5 5.7": ["incentivizing"], "9.4 7.0 18.8": ["geranium"], "18.4 -4.2 16.7": ["ped"], "10.2 3.9 13.7": ["substructure"], "3.5 17.3 28.3": ["whitetails"], "2.1 14.6 6.5": ["refraction"], "2.5 7.0 25.4": ["culturing"], "0.5 11.4 2.1": ["eyewash"], "4.1 1.8 -6.7": ["potholed"], "-5.8 16.7 -7.4": ["indoctrinating"], "-10.2 16.9 24.9": ["bowhunting"], "5.7 11.9 -1.1": ["pacesetting"], "-16.4 10.1 1.6": ["probative"], "3.4 10.8 -3.2": ["unproved"], "-7.2 4.7 26.2": ["pinot"], "5.7 4.2 11.0": ["qui"], "20.7 8.5 9.9": ["skylines"], "6.8 14.3 4.1": ["firestorms"], "1.4 27.9 16.7": ["ensign"], "-4.2 6.0 -2.4": ["showerhead"], "1.9 18.8 8.1": ["essences"], "7.7 1.4 26.4": ["tinned"], "3.5 7.6 3.1": ["metamaterials"], "5.3 18.5 1.4": ["damnedest"], "5.0 14.2 1.4": ["unclench"], "9.8 5.6 1.5": ["crackerjack"], "8.1 9.9 13.4": ["fended"], "2.2 14.5 -0.1": ["eurosceptic"], "13.4 3.8 11.3": ["accouterments"], "12.8 23.2 31.3": ["invertebrate"], "24.9 19.0 10.5": ["tumbleweed"], "10.6 0.2 11.1": ["skyway"], "6.4 16.7 16.8": ["scalper"], "4.8 11.1 1.1": ["panders"], "19.1 7.0 26.9": ["mastodon"], "2.5 10.7 23.0": ["windsurfers"], "-1.3 10.4 23.7": ["fruiting"], "5.9 -4.8 10.5": ["banjos"], "-3.8 11.8 7.7": ["perfectionists"], "-2.6 8.7 13.0": ["mucous"], "5.4 12.1 -0.4": ["instrumented"], "-0.5 4.0 17.6": ["dram"], "-2.6 -0.7 -2.6": ["paediatricians"], "-5.2 7.2 6.5": ["slackness"], "7.0 6.0 3.6": ["decamp"], "7.7 10.3 12.0": ["bargainers"], "-7.5 -2.0 0.9": ["outstation"], "-1.1 21.3 -1.5": ["cellmates"], "-0.3 -0.3 15.9": ["gigalitres"], "28.0 13.7 11.7": ["totems"], "0.0 11.5 5.1": ["placegetter"], "10.1 23.4 7.3": ["homophobes"], "12.1 0.5 5.2": ["semitrailers"], "1.5 10.3 6.9": ["floorplan"], "4.6 10.9 9.2": ["preconception"], "1.6 1.2 3.5": ["countercultural"], "11.9 -4.6 5.6": ["noughties"], "-1.7 12.0 3.4": ["accelerants"], "-4.0 7.7 7.7": ["reinsman"], "-2.4 2.9 8.4": ["glycogen", "memer"], "3.7 8.6 6.0": ["engraver"], "19.5 12.5 9.1": ["plonk"], "4.1 5.0 7.7": ["lobotomy"], "-0.0 7.6 5.7": ["nonissue"], "2.1 3.2 -0.6": ["beautified"], "0.9 2.7 -0.6": ["agronomists"], "12.0 -5.5 15.2": ["wrappings"], "15.2 17.1 10.4": ["megabanks"], "3.4 3.5 2.4": ["politicans"], "1.5 4.4 8.0": ["transposition", "glycerides"], "3.4 4.9 4.9": ["esophageal"], "-1.6 7.7 7.8": ["subdividing"], "8.2 12.9 5.1": ["competiton"], "11.5 8.2 13.3": ["capriciously"], "1.6 12.7 5.9": ["kibbutzim", "oligoastrocytoma"], "-1.9 2.0 2.8": ["refractive"], "9.6 16.1 13.7": ["twitches"], "8.2 11.3 19.3": ["becalmed"], "5.6 0.3 -4.9": ["unblocking"], "-1.7 0.9 9.6": ["flautist"], "-4.5 0.6 5.9": ["methylphenidate"], "-7.3 16.0 2.7": ["diarist"], "4.0 9.7 25.9": ["seacoast"], "19.2 15.4 7.9": ["slays"], "8.9 9.4 2.0": ["inanity"], "5.0 7.1 3.9": ["disproves"], "-11.1 2.6 4.3": ["eveningwear"], "8.4 5.0 6.2": ["decomposes"], "0.5 1.7 -3.1": ["architecting"], "-3.7 13.1 -1.4": ["misallocation"], "-3.7 5.2 3.3": ["quintile"], "1.6 3.4 2.6": ["neatness"], "-2.1 7.6 10.9": ["overindulge"], "5.5 2.2 15.6": ["tearoom"], "3.0 2.0 5.9": ["fusions"], "6.4 6.6 8.2": ["curtained"], "20.4 4.0 -6.3": ["renames"], "-4.1 10.1 4.1": ["demerit"], "2.5 7.1 4.2": ["mispronounced"], "6.7 10.6 9.0": ["methinks"], "3.0 5.7 5.5": ["touchingly"], "-10.1 3.2 4.4": ["hydrologic"], "1.0 14.9 10.1": ["flankers"], "3.2 17.5 2.2": ["intrusiveness"], "5.6 13.0 14.6": ["treetop"], "-1.9 -0.6 7.6": ["polymorphism"], "-1.5 -2.0 7.1": ["dyslipidemia"], "-5.1 -0.4 10.1": ["multivendor"], "8.9 25.3 3.7": ["pakistan"], "0.2 5.7 5.2": ["parring"], "16.2 7.6 17.0": ["lasses"], "7.5 7.6 4.9": ["disconcerted"], "-6.2 7.7 2.5": ["juco"], "4.3 6.5 15.6": ["swoons"], "4.8 9.1 10.9": ["monied"], "11.4 8.3 11.5": ["meow"], "-4.9 5.3 11.8": ["isoflavones"], "9.3 6.7 5.2": ["stockmarkets"], "3.3 26.6 6.6": ["dissembling"], "15.4 -3.1 -0.3": ["writeoffs"], "-3.1 7.0 11.2": ["anthocyanins"], "-5.8 6.4 7.3": ["otolaryngology"], "2.0 8.9 7.8": ["tangentially"], "4.3 -0.2 9.8": ["luxuriously"], "-1.6 20.2 8.3": ["typhus"], "14.4 11.8 10.8": ["soothsayer"], "0.3 4.2 19.3": ["patois"], "9.9 2.5 13.9": ["pandal"], "17.6 36.5 15.2": ["minion"], "-5.1 7.5 9.5": ["talky"], "-0.3 0.5 9.4": ["debarment"], "-5.3 7.4 8.8": ["ciders"], "-5.4 8.0 6.3": ["verisimilitude"], "5.9 4.2 11.8": ["ruff"], "-12.4 -0.1 5.9": ["doula"], "-1.0 10.8 8.6": ["ginning"], "11.8 3.9 19.8": ["agate"], "0.1 19.6 18.0": ["homie"], "6.0 -0.7 9.4": ["scions"], "4.1 2.8 8.1": ["storybooks"], "9.7 5.8 17.9": ["mouthfuls"], "2.7 7.8 -1.5": ["worshipful"], "20.2 0.5 13.0": ["wrangler"], "4.6 8.1 17.2": ["cored"], "8.8 -2.4 11.1": ["jag"], "4.7 8.2 6.0": ["tracklisting"], "0.5 4.8 1.8": ["recuse"], "-6.4 5.8 5.7": ["bunked"], "14.6 3.3 12.2": ["zoological"], "2.5 15.2 9.8": ["hallucinogens"], "10.9 5.4 10.8": ["tetchy"], "-3.7 0.1 6.4": ["gaveled"], "-4.5 5.2 8.0": ["revascularization"], "7.4 1.0 9.5": ["rw"], "0.0 3.4 6.5": ["logjams"], "-1.6 13.2 0.9": ["microburst"], "12.0 2.9 5.7": ["naff"], "2.9 3.0 4.3": ["triplex", "actresss"], "-5.1 17.0 -3.6": ["uncompromisingly"], "4.9 -0.6 4.5": ["biomaterial"], "4.9 9.1 4.1": ["restiveness"], "4.4 4.6 6.7": ["electroporation"], "2.1 8.4 -3.0": ["daresay"], "-1.5 -3.3 0.6": ["submitters"], "15.3 6.3 -3.0": ["blotting"], "3.1 6.6 13.0": ["wallplanners"], "16.5 8.2 17.8": ["elfin"], "10.3 6.7 6.0": ["caldera"], "15.8 34.1 16.8": ["mech"], "1.2 6.8 16.3": ["arborists"], "-1.3 10.3 6.3": ["semiconscious"], "8.2 -3.6 8.8": ["becquerels"], "-0.1 8.9 -8.0": ["communiques"], "8.7 14.3 13.8": ["arrowed"], "7.1 13.0 4.5": ["stoutly"], "-13.4 6.9 2.1": ["enplanements"], "2.0 0.4 9.5": ["riffed"], "0.3 11.5 7.5": ["harami"], "-0.3 7.1 9.4": ["congregant"], "-1.2 15.0 7.9": ["interdependencies"], "9.0 10.9 9.0": ["redrew"], "8.5 -1.7 11.0": ["playhouses"], "-1.4 6.0 4.8": ["triclosan"], "-5.2 1.7 7.1": ["misidentification"], "-6.6 2.2 -1.8": ["normalizes"], "10.9 -1.2 -1.7": ["ind"], "1.7 5.4 4.2": ["mellifluous"], "2.8 11.8 5.1": ["impertinent"], "0.7 7.3 -1.1": ["workwear"], "0.2 8.3 7.3": ["gingivitis"], "1.3 0.2 6.1": ["bicentenary"], "10.4 2.5 1.5": ["eircom"], "8.5 -1.8 9.1": ["som"], "9.5 15.6 3.7": ["subliminally"], "21.5 3.9 9.7": ["cavort"], "-2.3 12.3 11.5": ["gerrymandered"], "-2.2 8.3 5.4": ["circumspection"], "10.3 14.7 0.3": ["astonish"], "2.9 4.4 8.9": ["auds"], "-6.7 0.6 4.2": ["risperidone"], "3.5 8.1 5.2": ["exemplars"], "6.4 6.0 2.8": ["giveth"], "-1.0 -2.0 7.1": ["transgenders"], "10.1 8.9 9.4": ["indentations"], "12.1 8.9 18.8": ["marsupials"], "-4.0 12.6 3.8": ["cordiality"], "0.9 14.1 -3.1": ["harrassment"], "10.1 4.1 -1.2": ["salesforce"], "-10.4 13.3 3.6": ["layovers"], "-1.3 6.9 10.1": ["druggie"], "3.0 2.6 7.3": ["prerace"], "0.9 5.9 11.5": ["intersex"], "1.5 -1.3 11.1": ["splurges"], "4.2 4.6 8.3": ["microbiologists"], "-4.3 5.7 1.4": ["dissapointed"], "9.1 5.4 4.3": ["howlers"], "7.4 11.3 23.2": ["shiner"], "7.3 -4.7 4.6": ["yester"], "6.2 5.2 4.5": ["siphons"], "2.4 20.1 4.7": ["irredeemable"], "4.2 30.8 10.9": ["lethally"], "18.2 -6.7 5.8": ["rustled"], "15.8 11.4 6.3": ["inconsiderable"], "3.9 20.9 9.5": ["tentpole"], "9.4 12.2 4.0": ["wholes"], "2.2 2.8 4.2": ["ty"], "1.7 3.1 13.9": ["jo"], "-6.6 8.3 -4.6": ["sportiness"], "15.1 5.8 5.4": ["sony"], "1.2 19.4 8.4": ["irretrievable"], "11.8 6.3 10.0": ["expectantly"], "-2.5 14.3 13.7": ["breastbone"], "3.2 6.3 -1.0": ["postcolonial"], "6.5 -2.2 4.2": ["haircare"], "10.6 8.2 0.3": ["trounces"], "2.5 2.4 5.9": ["piccolo"], "13.2 20.5 6.3": ["skulking"], "5.4 21.3 4.8": ["inescapably"], "5.2 4.7 17.6": ["mica"], "-2.7 5.3 -3.8": ["newsweekly"], "0.8 8.7 9.4": ["touristic"], "7.8 10.2 15.0": ["etymology"], "4.0 10.5 -0.9": ["inductive"], "5.1 -0.8 1.7": ["hearkens"], "7.5 8.0 5.8": ["agrochemicals"], "12.5 18.3 4.0": ["unquantifiable"], "-6.4 11.6 7.4": ["protestant"], "10.3 9.7 14.1": ["toupee"], "8.8 16.6 10.5": ["uselessness"], "-0.6 2.0 5.1": ["plats"], "-8.3 3.9 5.6": ["latencies"], "9.9 2.7 4.8": ["soporific"], "-5.0 12.8 3.3": ["requester"], "2.0 -0.4 -6.9": ["refurbishes"], "2.9 7.0 13.8": ["ornithologists"], "8.2 16.7 10.7": ["cooperators"], "2.2 2.5 3.7": ["afterthoughts"], "-0.1 0.9 -5.7": ["helplines"], "-9.9 6.8 6.1": ["detainer"], "-0.4 9.0 3.0": ["undertrials"], "-15.4 5.7 2.2": ["readmissions"], "2.8 8.9 15.8": ["riverbeds"], "2.5 7.4 3.3": ["cosmetically"], "-3.5 6.8 6.1": ["anglophone"], "-0.5 1.9 19.0": ["longhouse"], "2.2 -5.1 7.8": ["jumpstarted"], "3.0 16.0 7.0": ["impurity"], "2.1 1.3 5.3": ["extravagances"], "17.3 3.9 8.4": ["hieroglyphics"], "0.9 -2.2 17.5": ["upfronts"], "7.4 9.4 11.0": ["devoutly"], "9.1 9.1 14.9": ["adorably"], "10.2 3.6 12.9": ["hoedown"], "5.0 8.8 5.9": ["prides"], "7.5 6.7 10.6": ["humbler"], "-1.6 4.7 8.2": ["codifies"], "6.5 5.1 1.8": ["reformatting"], "15.1 10.3 4.0": ["hillbillies"], "-1.0 11.4 4.3": ["teetotaler"], "8.1 8.7 5.7": ["etisalat"], "12.1 10.5 14.1": ["thang", "chiseling"], "-6.4 6.2 9.1": ["reenacted"], "9.9 40.6 11.5": ["nemeses"], "6.9 21.7 11.6": ["rationalism"], "26.7 12.0 19.6": ["pygmies"], "1.0 18.3 12.1": ["supremacist"], "1.2 8.3 7.2": ["deducts"], "2.4 11.8 3.4": ["ordinariness"], "9.7 10.1 1.9": ["blacker"], "4.8 17.2 -1.5": ["bioweapons"], "16.6 -0.3 1.9": ["rumpus"], "3.3 5.0 -1.5": ["treatises"], "-3.4 15.7 9.9": ["hotheaded"], "8.1 34.2 4.2": ["cyberwar"], "-1.7 9.6 6.7": ["pastureland"], "-2.5 13.3 9.7": ["breathers"], "17.3 -1.7 19.4": ["cockatoo"], "10.6 1.2 3.9": ["smarten"], "10.6 -0.3 16.5": ["clucking"], "2.5 6.6 1.8": ["unpersuasive"], "8.7 1.6 1.8": ["het"], "6.4 20.6 -1.5": ["disingenuously"], "2.9 7.7 1.8": ["heartbreaks"], "5.4 11.4 3.2": ["officious"], "7.4 5.5 -3.6": ["convulsion"], "-6.1 4.1 10.2": ["drabs"], "-0.3 2.8 16.7": ["crosswise"], "10.1 13.0 0.7": ["hypocritically"], "3.5 8.2 0.7": ["affronted"], "11.1 15.5 29.2": ["drumstick"], "5.2 12.1 5.1": ["backheel"], "7.9 3.4 3.9": ["junking"], "9.6 6.0 8.4": ["proffering"], "5.2 12.1 -0.3": ["desensitization"], "17.6 9.0 10.2": ["hallelujah"], "17.5 4.9 15.0": ["matchsticks"], "10.7 1.8 7.4": ["speediest"], "1.5 15.1 5.7": ["avenges"], "-3.1 8.6 3.6": ["psalms"], "7.2 4.3 10.2": ["paunch"], "-3.1 11.5 15.2": ["depopulation"], "1.7 8.6 6.0": ["wormed"], "2.0 9.3 2.6": ["aback"], "-2.3 -0.5 8.6": ["streetwear", "guarenteed"], "8.2 12.7 5.5": ["inchoate"], "1.4 7.4 2.8": ["hazed"], "-0.5 -2.9 7.5": ["hairstylists"], "-4.9 17.8 3.2": ["disempowered"], "-0.2 -1.6 3.4": ["pantsuits"], "-2.2 -0.2 0.2": ["watermarking"], "11.2 17.0 2.7": ["unalloyed"], "1.6 3.1 0.5": ["quieten"], "17.7 10.0 13.1": ["miasma"], "14.4 5.1 14.1": ["roils"], "9.1 5.1 12.2": ["togs"], "0.2 8.5 11.7": ["theorem"], "-9.7 10.5 7.5": ["arterials"], "-1.9 5.8 -3.5": ["declaratory"], "1.5 13.4 19.0": ["foraged"], "6.8 21.1 11.8": ["perps"], "-7.1 4.7 4.6": ["laparoscopy"], "8.0 0.5 13.3": ["dwarfism"], "5.6 11.4 6.6": ["dander"], "0.5 4.6 6.0": ["angsty"], "1.5 15.8 2.7": ["reemerge"], "-1.7 6.5 6.4": ["psychotherapists"], "6.1 13.0 7.5": ["alighting"], "-4.7 -4.3 5.0": ["noncontroversial"], "26.0 7.0 3.9": ["beleagured"], "0.1 12.6 14.0": ["befalls"], "-3.1 11.9 11.1": ["legside"], "12.8 12.3 24.5": ["fixin"], "9.6 -3.8 6.5": ["curios"], "5.9 3.2 6.2": ["primping"], "1.3 3.1 1.0": ["catalysis"], "-5.2 10.9 2.4": ["argumentation"], "-9.0 5.2 5.3": ["ligature"], "17.4 20.4 6.9": ["slinking"], "-4.2 18.2 11.3": ["quinine"], "-1.7 2.4 7.1": ["aseptic"], "-1.6 -3.4 3.8": ["overrepresented"], "0.1 8.4 23.7": ["doneness"], "5.5 13.5 7.5": ["rakish"], "4.2 -4.1 -1.1": ["cont"], "2.4 9.5 8.5": ["contrive"], "1.3 23.3 3.2": ["proliferators"], "10.0 -0.3 4.7": ["typographical"], "0.4 -2.3 5.3": ["scriptwriting"], "-4.2 -0.2 -3.8": ["specifiers"], "10.1 8.4 26.2": ["aubergine"], "12.0 1.1 5.8": ["nestles"], "-2.6 5.5 10.7": ["spillways"], "-6.8 12.9 -2.1": ["antisemitic"], "-0.2 4.2 19.7": ["runabout"], "-0.2 -4.7 5.4": ["resealed"], "5.4 7.4 3.5": ["enthroned"], "0.2 7.9 1.3": ["boceprevir"], "13.2 13.6 14.8": ["goggle"], "0.6 16.9 11.7": ["underthrown"], "3.3 3.8 5.6": ["mistrials"], "4.7 2.2 8.6": ["hobnob"], "-6.1 -2.3 0.2": ["misclassified"], "7.1 2.4 3.4": ["synchrotron"], "-2.5 3.1 7.3": ["immunoassay"], "3.0 6.9 12.3": ["flickr"], "-6.1 5.2 4.3": ["sonatas"], "-4.3 18.4 6.8": ["transgress"], "-1.9 6.6 4.5": ["unbudgeted"], "4.7 13.8 21.5": ["sunrises"], "8.4 8.5 0.2": ["leafleting"], "-1.9 4.9 4.3": ["particulary"], "13.9 -0.4 12.2": ["suckling"], "12.2 20.3 15.6": ["stingers"], "14.3 5.3 5.7": ["contortionist"], "16.3 3.6 7.2": ["marts"], "0.2 3.5 -2.2": ["reconstructs"], "8.0 9.9 5.8": ["penitent"], "12.6 -0.4 13.0": ["gyrate"], "0.3 3.5 -3.1": ["glamorize"], "1.4 10.8 7.1": ["witticisms"], "5.0 18.4 4.4": ["leftie"], "8.5 10.5 18.6": ["granary"], "5.7 4.3 9.6": ["daffy"], "5.6 20.2 4.9": ["unrelentingly"], "11.6 5.6 1.7": ["outslugged"], "3.4 8.5 2.0": ["slickness"], "6.3 7.0 16.9": ["storeowners"], "5.0 3.5 -1.1": ["hearken"], "8.7 14.2 7.0": ["acrobatically"], "5.0 0.2 20.8": ["jin"], "2.6 6.5 4.0": ["multigoal"], "-5.8 9.4 27.0": ["fishable"], "7.4 34.7 7.7": ["encirclement"], "0.8 -1.6 5.5": ["lactate"], "11.6 2.2 18.5": ["tuft"], "-2.8 11.1 4.8": ["rehydrate"], "2.3 7.1 4.6": ["gloomiest"], "3.0 14.7 -2.5": ["deactivating"], "11.5 1.1 11.5": ["hoofed"], "-0.4 3.8 11.0": ["coinsurance"], "8.6 -0.5 9.6": ["wholesomeness"], "3.2 14.8 2.6": ["beeper"], "2.2 4.3 10.4": ["pedestrianized"], "3.0 4.5 6.3": ["wii"], "7.5 5.7 17.1": ["faire"], "1.6 4.0 11.4": ["valets"], "-0.7 7.5 7.4": ["brainers"], "20.8 6.6 3.6": ["huckster"], "17.5 -1.4 10.3": ["venders"], "-3.8 6.8 12.2": ["chargebacks"], "0.7 6.8 2.4": ["coefficients"], "-4.7 18.5 7.2": ["cinematics"], "4.8 9.9 15.9": ["concocts"], "-3.2 -0.7 3.7": ["dietetics"], "11.7 1.8 4.7": ["tearaway"], "1.1 12.0 5.9": ["edification"], "2.7 11.5 3.8": ["rebs"], "4.3 3.0 -0.9": ["sublicense"], "11.7 10.7 12.9": ["wonk"], "-1.1 6.6 11.4": ["hindi"], "0.7 14.4 8.5": ["idolizes"], "9.9 7.1 16.4": ["japan"], "-9.9 6.9 -0.6": ["molestations"], "4.8 16.0 5.5": ["indians"], "-6.7 7.5 4.8": ["cannabinoids"], "-7.9 9.2 2.5": ["resubmission"], "6.5 14.6 8.9": ["reloads"], "10.1 7.6 6.8": ["beheld"], "-1.4 6.6 9.4": ["divulges"], "0.7 2.3 -1.1": ["nondisclosure"], "3.6 5.3 12.2": ["capoeira"], "-0.4 14.5 6.4": ["corruptions"], "7.0 6.0 5.8": ["atlases"], "7.2 2.9 25.4": ["microalgae"], "14.7 -3.8 0.8": ["burgeoned"], "-5.3 5.7 -0.6": ["dyspnea"], "5.3 7.3 25.8": ["longshoreman"], "1.8 -0.8 4.8": ["configures"], "-5.7 4.7 8.6": ["epithermal"], "10.3 12.9 12.9": ["blotches"], "8.5 3.3 5.7": ["palming"], "-6.7 9.8 9.2": ["mids"], "23.8 5.3 18.5": ["thimble"], "1.9 8.8 1.1": ["refering"], "10.3 4.1 14.1": ["saggy"], "6.3 -3.4 14.5": ["bunkhouse"], "-1.7 6.2 3.4": ["gabapentin"], "-2.8 5.4 12.2": ["vibraphone"], "9.5 16.0 9.3": ["ites"], "-2.3 0.0 3.0": ["macauhub"], "-3.4 30.2 10.0": ["munition"], "-4.5 6.4 6.0": ["sojourns"], "16.2 5.0 6.2": ["flagships"], "14.8 23.3 32.4": ["nutcracker"], "2.9 2.4 27.3": ["kielbasa"], "1.0 10.9 6.2": ["misheard"], "21.0 0.9 2.4": ["chugs"], "11.9 0.7 22.7": ["yum"], "-3.6 6.5 1.4": ["autoimmunity"], "-1.8 -6.6 -0.4": ["tions"], "11.1 4.3 4.1": ["september"], "7.8 3.3 -2.6": ["innovativeness"], "8.6 9.3 7.8": ["makin"], "3.6 6.2 29.9": ["drydock"], "11.0 1.2 2.6": ["nailbiting"], "5.1 2.2 -1.5": ["ein"], "8.8 21.4 5.4": ["unmentionable"], "30.6 25.3 31.0": ["tentacle"], "5.5 1.7 4.7": ["fabricates"], "-1.2 1.8 3.1": ["shortchanges"], "8.7 10.2 9.3": ["unsubtle"], "7.3 12.5 10.1": ["chromatic"], "5.3 17.9 1.0": ["commiserating"], "-5.5 3.3 10.5": ["snowplowing"], "11.4 1.9 28.2": ["smokehouse"], "3.1 0.9 -1.1": ["synthesizes"], "7.6 8.2 -2.6": ["adjoin"], "16.8 7.1 8.7": ["protrudes"], "7.7 4.7 -6.1": ["overusing"], "11.3 7.7 20.9": ["aquamarine"], "9.0 8.0 24.0": ["dabs"], "17.3 32.9 11.1": ["phantoms"], "7.7 8.5 18.8": ["emus"], "12.2 -0.0 6.9": ["trln"], "9.8 11.8 7.7": ["impactor"], "6.0 -2.8 2.2": ["ger", "diabetology"], "7.5 15.3 8.5": ["sine"], "6.4 3.4 -1.9": ["ergonomically"], "12.9 -2.8 0.0": ["multiuse"], "9.2 13.9 2.3": ["scowled"], "11.1 6.4 31.1": ["duckling"], "14.7 -3.1 5.5": ["ponying"], "16.6 14.2 9.0": ["slobbering"], "23.5 1.5 1.8": ["spurting"], "8.8 10.7 10.8": ["hobos"], "8.9 4.5 8.6": ["childs"], "14.9 6.3 4.1": ["trudges"], "2.2 10.1 4.3": ["typecasting"], "5.2 1.4 14.3": ["tim"], "9.4 4.2 0.4": ["shakiness"], "-0.8 2.7 9.7": ["tinting"], "3.0 2.7 3.9": ["procrastinated"], "8.6 10.1 3.3": ["orienting"], "-11.4 10.1 0.6": ["astigmatism"], "-1.9 -3.5 3.3": ["escrowed"], "-2.3 11.2 3.1": ["conjectures"], "-0.6 11.6 0.4": ["hemorrhages"], "15.5 7.7 16.0": ["yonder"], "13.1 6.9 8.3": ["pinnacles"], "10.5 8.8 7.6": ["broomsticks"], "8.0 13.4 10.8": ["hillock"], "7.7 7.0 30.1": ["kibble"], "7.4 18.7 4.1": ["unthreatening"], "12.1 4.9 19.6": ["vaudevillian"], "-5.0 1.5 14.1": ["tuxes"], "-4.5 6.5 1.6": ["echocardiogram"], "8.1 4.5 12.0": ["sandblasted"], "1.9 10.2 2.9": ["pacey"], "8.3 9.5 5.1": ["googling"], "-1.1 2.3 10.3": ["shotput"], "16.3 8.8 9.8": ["geometrically"], "8.8 24.8 3.2": ["zealotry"], "9.5 1.0 12.5": ["california"], "4.8 7.8 6.7": ["gabbing"], "-0.6 3.3 8.1": ["optoelectronic"], "19.1 8.2 4.3": ["cratering"], "3.3 6.9 11.3": ["quickstep"], "18.1 17.5 2.6": ["omnipotence"], "4.9 0.4 3.0": ["wised"], "-5.5 8.0 41.0": ["sportfishing"], "1.4 2.1 16.1": ["interprovincial"], "10.8 15.2 5.6": ["dimly"], "2.7 -5.9 6.8": ["beauticians"], "3.5 12.3 7.0": ["cheapening"], "2.3 6.4 13.9": ["reheating"], "16.8 10.5 9.0": ["wilts"], "0.7 18.2 19.2": ["sonnet"], "19.1 5.1 -1.5": ["extractor"], "6.8 11.1 8.7": ["bogging"], "6.9 22.8 8.5": ["nutter"], "-3.8 0.6 6.1": ["polymetallic"], "8.4 12.1 4.5": ["excitingly"], "4.6 18.0 6.3": ["unreconstructed"], "8.0 6.8 7.9": ["exurbs"], "-3.0 7.8 6.0": ["undereducated"], "-4.8 13.9 1.7": ["xvi"], "10.2 17.3 4.8": ["gulags"], "3.9 21.2 11.7": ["thine"], "1.8 12.7 -3.9": ["uncharitable"], "-0.3 -0.8 1.1": ["kaufen"], "8.2 5.9 11.9": ["ironworker"], "-10.4 10.7 15.5": ["unallotment"], "3.7 3.1 12.8": ["pickin", "dryspell"], "0.7 2.5 18.3": ["pedicab"], "-9.8 4.8 0.5": ["alcohols"], "-0.3 8.5 11.7": ["pitchout"], "6.5 22.1 11.4": ["polygon"], "1.2 14.4 10.2": ["eviscerating"], "8.5 6.3 4.3": ["tightfisted"], "10.4 5.1 12.7": ["paul"], "-4.6 3.5 20.7": ["strandings"], "3.5 8.4 9.8": ["galls"], "9.5 4.7 4.8": ["idles"], "9.8 7.9 1.2": ["outdoes"], "1.2 4.7 1.1": ["fitment"], "8.7 -1.2 12.0": ["bodysuits"], "6.2 14.2 14.1": ["exultation"], "-6.9 2.7 4.2": ["slippages"], "4.2 23.1 7.6": ["amnesiac"], "9.4 10.7 -4.8": ["conceptualizing"], "9.0 9.0 11.1": ["sluice"], "1.9 7.0 2.4": ["autographing"], "3.9 3.0 14.2": ["singletons"], "2.6 10.3 3.3": ["barnburner"], "0.2 1.5 5.2": ["curation"], "2.7 5.9 13.1": ["breccias"], "4.5 12.0 6.7": ["impudent"], "13.2 -0.7 14.2": ["dosh"], "12.6 15.1 4.2": ["contort"], "3.0 12.0 11.1": ["imaginings", "drovers"], "0.7 8.4 19.4": ["multihull"], "13.1 2.7 11.2": ["stagehand"], "-0.4 12.5 8.1": ["airhead"], "-7.2 9.9 -0.4": ["billeted"], "-2.8 3.3 6.7": ["inductors"], "8.9 1.0 10.3": ["filigree"], "-2.2 18.3 3.3": ["abridging"], "0.6 12.5 5.8": ["discontinuity"], "-1.2 6.4 7.3": ["moodiness"], "7.4 12.4 9.4": ["demarcating"], "0.3 1.7 27.0": ["flavourful"], "1.0 14.5 5.8": ["strategise"], "3.2 1.1 1.9": ["nanomedicine"], "6.8 10.9 11.2": ["airgun"], "16.4 11.6 11.4": ["zigzags"], "11.8 -0.4 25.6": ["beignets"], "23.8 14.4 25.4": ["glob"], "3.6 6.0 1.7": ["ordinaries"], "8.7 19.8 4.6": ["thoughtlessly"], "7.5 -0.4 8.3": ["thesp"], "6.9 4.0 -0.7": ["ructions"], "5.4 23.4 2.6": ["destructiveness"], "0.4 6.1 -0.2": ["callouts"], "-0.3 12.8 9.6": ["birdshot"], "13.7 8.3 10.8": ["chalkboards"], "3.0 14.7 9.4": ["milquetoast"], "-2.1 -0.5 7.2": ["matronly"], "-1.2 5.3 8.0": ["playdates"], "-6.3 3.6 9.5": ["amniocentesis"], "-4.0 10.2 14.7": ["claimers"], "6.4 4.6 10.3": ["campervan"], "4.8 -4.6 4.1": ["glammed"], "13.9 7.4 17.6": ["congealed"], "10.3 4.5 8.9": ["handprint"], "10.0 23.8 8.0": ["tracers"], "12.6 6.8 7.0": ["tramps"], "-8.7 11.2 9.9": ["adit"], "6.4 19.5 -0.0": ["soviet"], "3.4 13.7 -7.2": ["purifies"], "8.9 8.3 7.3": ["hopers"], "6.5 7.0 6.3": ["transparencies"], "9.5 9.3 18.1": ["lanai"], "-5.1 2.8 5.4": ["fleshes"], "2.6 9.6 3.0": ["nucleotide"], "-2.4 4.9 -7.9": ["familiarizing"], "-4.5 4.1 11.5": ["recalculation"], "6.6 8.4 1.8": ["reponse"], "8.5 11.8 2.4": ["bamboozle"], "6.4 4.8 6.4": ["ic"], "16.6 10.1 30.7": ["firefly"], "-0.4 10.0 3.0": ["incurrence"], "-8.2 17.9 0.1": ["impugning"], "-6.9 4.1 8.0": ["hryvnia"], "5.3 4.6 8.8": ["amalgamations", "audioguide"], "11.2 3.1 8.0": ["riverwalk"], "0.7 -0.3 8.2": ["wrapup"], "-1.5 7.9 3.1": ["stowage"], "-3.4 14.2 0.5": ["monarchist"], "12.5 4.8 6.2": ["experimenters"], "9.3 11.2 18.7": ["cottonwood"], "8.4 2.7 11.6": ["gable"], "4.4 -1.3 4.6": ["smoothen"], "14.2 11.9 15.1": ["gob"], "-4.8 4.9 10.3": ["contestable"], "17.4 1.9 9.3": ["sturdiness"], "1.3 2.5 6.4": ["webisode"], "-6.3 22.5 14.3": ["privation"], "13.0 4.7 0.9": ["centrifugal"], "2.8 12.8 4.6": ["prevarication"], "10.5 0.3 0.1": ["november"], "5.9 13.5 16.0": ["pulpy"], "6.3 9.9 6.4": ["fuselages"], "0.4 7.1 3.4": ["comas"], "7.0 -1.8 2.8": ["managment"], "-6.5 7.7 0.2": ["recollects"], "-5.3 9.1 4.2": ["pitstops"], "0.7 8.1 8.5": ["antisense"], "6.8 3.3 2.5": ["shakeups"], "-1.1 15.9 -0.9": ["callings"], "2.4 12.9 15.3": ["trouper"], "14.2 -1.9 2.9": ["downmarket"], "-1.8 4.1 11.5": ["graining"], "-2.2 3.1 0.5": ["insoles"], "-6.2 7.8 11.8": ["overgrazing"], "4.3 1.1 12.2": ["sheaths"], "4.7 7.5 13.0": ["daters"], "6.6 7.5 25.5": ["slipway"], "6.7 4.8 -0.5": ["modernizes"], "4.0 16.4 6.1": ["personages"], "8.1 4.0 1.5": ["flays"], "21.0 12.7 14.6": ["parasol"], "-0.4 26.0 1.7": ["cyberwarfare"], "1.3 3.0 0.5": ["peripherally"], "1.0 7.5 0.6": ["strangulated"], "10.0 9.9 15.5": ["hungriest"], "1.7 12.5 20.1": ["tines"], "10.9 7.7 19.1": ["japanese"], "0.6 12.3 17.4": ["monohull"], "11.7 6.9 1.2": ["underperformer"], "-1.6 15.7 8.7": ["handedly"], "2.9 6.3 13.3": ["righthanders"], "11.1 -3.3 18.7": ["sal"], "4.9 13.7 12.0": ["newsreel"], "-2.3 -0.0 7.3": ["logbooks"], "3.3 7.5 -5.5": ["disassociated"], "10.8 5.8 32.0": ["lasagne"], "2.4 11.2 10.7": ["crosscurrents"], "5.9 7.9 22.8": ["paler"], "3.0 5.9 5.3": ["unbuilt"], "9.8 7.4 5.8": ["realy"], "5.4 8.1 12.2": ["speedskater"], "-3.0 0.8 17.7": ["pawnbroker"], "1.5 0.9 5.7": ["epigenetics"], "4.1 10.8 7.6": ["heatwaves"], "13.8 10.5 -8.3": ["paragons"], "8.5 8.0 12.8": ["invitingly"], "2.7 -1.0 3.9": ["naproxcinod"], "19.6 5.1 17.0": ["lumberjacks"], "1.1 6.4 16.3": ["kabaddi"], "4.1 9.1 11.0": ["earmuffs"], "-2.6 3.0 4.3": ["countercyclical"], "6.1 13.3 23.1": ["deciduous"], "2.6 3.6 16.0": ["dorsal"], "-0.9 1.6 3.4": ["standardizes"], "7.8 4.7 -1.5": ["slickly"], "7.8 -0.2 13.8": ["snakeskin"], "9.2 -0.5 12.7": ["muesli"], "3.4 -1.0 5.0": ["bioactive"], "3.8 9.7 4.4": ["offeree"], "9.3 11.1 15.4": ["submersibles"], "6.9 1.8 1.8": ["wh"], "2.5 11.6 -6.7": ["personalizes"], "4.0 3.8 14.2": ["chamomile"], "-6.0 8.2 2.7": ["acclimatize"], "-14.0 1.0 -1.8": ["anticoagulation"], "14.3 5.9 0.9": ["bulks"], "2.2 6.5 5.5": ["checkbox"], "5.3 17.3 4.5": ["harasses"], "-0.9 6.9 5.1": ["inductor"], "6.8 8.9 6.8": ["carports"], "10.0 9.9 29.5": ["jumbos"], "-3.7 4.7 5.6": ["cliffhangers"], "-3.9 13.0 5.8": ["overthink"], "10.5 12.3 36.7": ["lamprey"], "4.3 6.9 35.7": ["flathead"], "4.8 12.6 8.4": ["babus"], "7.0 11.9 18.2": ["pika"], "2.1 3.1 10.8": ["glucagon"], "19.8 14.0 12.8": ["rubes"], "3.5 -1.1 6.7": ["penile"], "4.3 5.6 -1.8": ["outsells"], "-4.8 5.0 14.6": ["tithes"], "1.6 2.7 1.6": ["manats"], "17.1 9.3 7.2": ["pratfall"], "-5.7 11.1 -2.6": ["impulsiveness"], "7.1 9.9 5.5": ["prolifically"], "7.2 11.0 6.9": ["actualization"], "7.7 0.5 10.3": ["protruded"], "13.1 6.5 6.4": ["boondoggles"], "1.1 4.8 5.3": ["pharmacogenomics"], "9.7 8.2 7.4": ["sexing"], "2.0 18.9 2.7": ["badmouthing"], "4.3 11.1 0.6": ["misplacing"], "-1.0 9.2 -1.5": ["unconstitutionality"], "7.5 0.3 -1.0": ["focusses"], "1.8 10.0 11.7": ["friars"], "9.1 4.0 10.3": ["paperboy"], "3.1 7.4 6.5": ["satirize"], "11.9 15.0 14.9": ["jitterbug"], "6.9 8.3 18.3": ["viscera"], "0.9 8.7 5.6": ["sequestering"], "-7.7 -3.1 10.2": ["colostrum"], "0.1 3.6 7.9": ["backless"], "5.4 4.8 25.8": ["burro"], "9.7 6.7 13.2": ["nfl"], "5.5 10.3 2.9": ["couldn"], "9.1 25.3 4.6": ["hellfire"], "6.0 9.8 26.8": ["uneaten"], "0.4 3.4 8.2": ["accessorizing"], "8.5 21.5 5.1": ["chasms"], "5.1 6.7 4.5": ["resized"], "14.6 2.3 5.4": ["yodeling"], "-1.3 -0.4 4.2": ["redevelopments"], "7.8 5.4 8.7": ["bathhouses"], "-7.2 11.7 5.8": ["orators"], "10.2 6.7 17.9": ["sherbet"], "4.1 9.7 -0.3": ["synergize"], "4.0 9.0 7.3": ["postmodernism"], "2.9 -2.1 4.8": ["nuh"], "15.7 11.6 4.5": ["tumbleweeds"], "8.6 8.4 24.7": ["drippings"], "1.1 5.6 6.7": ["classicism"], "4.8 10.0 10.3": ["shoulda"], "7.3 13.7 0.8": ["imminence"], "2.7 20.5 10.9": ["statism"], "9.8 23.9 23.6": ["louse"], "-11.0 -5.3 6.6": ["waitlist"], "8.3 5.8 3.4": ["mutilations"], "-2.6 12.1 11.4": ["shrewdness"], "0.6 8.3 10.9": ["uncontaminated"], "-2.9 5.0 3.1": ["alternators"], "5.1 6.5 8.4": ["yogi"], "11.7 5.7 6.8": ["juicer"], "11.0 10.7 13.6": ["pawed"], "5.0 12.5 9.3": ["spitfire"], "19.6 13.1 4.2": ["tricksters"], "7.1 13.8 10.5": ["soma"], "4.6 0.7 19.5": ["martin"], "11.8 5.0 1.3": ["populates"], "10.4 1.4 7.8": ["mah"], "-10.8 7.8 -1.6": ["aliya"], "11.7 12.3 8.4": ["dejectedly"], "-7.4 1.6 2.9": ["listenable"], "6.7 26.6 8.3": ["subhuman"], "0.7 12.6 4.6": ["natured"], "-0.7 20.5 7.7": ["hittable"], "-2.0 12.7 0.2": ["rater"], "-12.3 2.0 -0.3": ["matriculate"], "9.5 4.1 12.2": ["kindergartener"], "0.6 -1.3 7.0": ["verged"], "8.0 18.3 7.0": ["unenlightened"], "6.6 17.7 31.7": ["nematode"], "11.0 11.5 19.3": ["aphrodisiacs"], "12.1 6.1 2.1": ["demystifying"], "7.6 6.2 10.5": ["kiddos"], "5.5 4.0 11.3": ["jangle"], "12.8 8.4 5.6": ["showmen"], "1.5 -1.9 4.8": ["newsy"], "14.0 6.6 11.5": ["pecs", "entranceways"], "3.6 -2.7 7.6": ["highschool"], "8.5 10.4 11.2": ["sexpot"], "3.7 7.2 1.6": ["profuse"], "7.0 14.1 8.3": ["steppe"], "3.2 2.4 0.6": ["airconditioning"], "8.7 16.9 6.8": ["cruellest"], "6.5 15.7 3.1": ["leitmotif"], "9.3 17.7 9.0": ["prisms"], "12.7 2.0 9.8": ["buttresses"], "3.2 13.5 11.8": ["cooperator"], "-5.2 10.6 22.7": ["nape"], "7.2 2.6 1.3": ["ry"], "1.1 14.1 16.1": ["pitbulls"], "3.6 13.2 6.5": ["brokenhearted"], "2.6 6.3 3.0": ["decathlete"], "6.8 22.1 9.3": ["shootdown"], "4.8 8.3 19.4": ["throated"], "0.1 14.0 31.5": ["crankbait"], "5.5 5.7 -1.4": ["responsibilty"], "6.0 12.6 12.3": ["biohazard"], "5.3 8.5 8.2": ["narcissists"], "-2.3 18.3 -1.3": ["mistrusted"], "-11.8 4.9 0.1": ["abstinent"], "-5.7 17.1 15.6": ["wildland"], "1.1 12.1 24.2": ["costal"], "5.0 6.9 2.8": ["deigned"], "-2.0 5.1 5.3": ["harmonium"], "3.9 7.2 9.9": ["sandstones"], "4.9 4.9 13.6": ["wallows"], "6.2 4.3 10.8": ["pouted"], "-9.1 11.2 7.4": ["heuristics"], "15.5 9.9 0.9": ["corporately"], "8.9 1.1 1.4": ["popularization"], "7.0 5.7 15.5": ["italian"], "-0.3 7.3 10.2": ["sunbathe"], "8.7 2.0 6.1": ["fs"], "11.5 11.9 27.8": ["lupine"], "8.6 17.3 11.1": ["haymaker"], "0.1 6.0 -5.7": ["prejudicing"], "5.5 3.6 -3.0": ["endows"], "-8.5 -0.1 30.0": ["collards"], "7.9 12.9 3.7": ["unsupportable"], "11.1 14.5 13.2": ["turnbuckles"], "16.5 12.5 2.9": ["hurtles"], "7.0 17.4 1.4": ["regroups"], "3.1 8.4 0.7": ["actuated"], "1.1 17.2 9.9": ["copilot"], "15.5 7.6 14.5": ["convex"], "10.1 9.0 3.2": ["subcategory"], "0.3 28.6 5.3": ["undefended"], "-3.9 2.0 7.2": ["chelation"], "0.4 3.5 -0.1": ["bioequivalence"], "8.7 9.2 9.8": ["busybody"], "-1.7 18.4 7.0": ["antiterror"], "4.2 1.8 8.1": ["dressmaker"], "0.3 3.8 8.2": ["potboiler"], "-2.9 6.7 12.8": ["playdowns"], "-0.6 7.0 7.2": ["enlivens"], "-2.7 3.8 5.2": ["cruciate"], "1.7 23.5 0.2": ["calumny"], "-3.1 17.3 -4.4": ["decrypted"], "5.0 13.5 28.2": ["toms"], "2.0 7.6 10.3": ["malformation"], "11.4 12.0 9.4": ["fractal"], "15.0 5.1 14.4": ["lolling"], "-0.7 12.6 17.2": ["interisland"], "-0.5 10.6 1.2": ["usurps"], "8.6 32.4 10.2": ["stratagem"], "5.3 -0.6 1.8": ["interstitial"], "-1.7 5.6 8.8": ["widebody"], "3.5 -1.6 14.3": ["ito"], "5.4 -3.0 12.1": ["lin"], "3.4 5.0 7.6": ["starched"], "3.2 3.7 14.2": ["hydrogel"], "-1.7 2.1 9.4": ["incandescents"], "12.9 3.0 8.4": ["canadian"], "-5.1 8.1 11.7": ["appellations"], "3.1 10.1 6.6": ["ndrangheta"], "5.7 8.3 6.5": ["rootless"], "-2.0 -0.6 11.8": ["pirfenidone"], "12.1 5.0 8.2": ["shrouding"], "0.7 -1.8 -2.2": ["fanless"], "3.3 3.4 13.9": ["mam"], "7.2 19.6 3.1": ["hypersonic"], "5.8 12.7 27.2": ["gourmets"], "8.2 8.0 15.8": ["har"], "7.9 15.8 23.5": ["rudders"], "7.3 9.3 6.4": ["execrable"], "9.0 10.4 3.4": ["contorting"], "3.5 -3.9 -0.7": ["hs"], "15.1 14.1 6.6": ["internets"], "-1.3 17.0 8.1": ["hydrazine"], "2.0 1.2 12.9": ["paypal"], "19.7 3.9 13.9": ["shambling"], "3.5 8.8 -0.7": ["reinterpreting"], "17.2 12.7 2.6": ["dystopia"], "-4.1 6.8 17.0": ["mushing"], "6.7 2.6 4.7": ["dulling"], "3.3 3.9 11.6": ["earthiness"], "-5.9 9.5 5.4": ["overdraw"], "12.1 5.7 9.2": ["handstand"], "4.5 -2.5 10.1": ["manicurist", "phonograms"], "8.3 13.7 11.6": ["deftness"], "-4.8 1.4 5.6": ["dystonia"], "-1.7 8.0 13.4": ["basting"], "-8.6 5.7 10.9": ["mixologist"], "7.3 1.3 6.4": ["tousled", "reprographer"], "-1.4 17.2 2.4": ["arguement"], "2.9 26.0 10.1": ["waypoints"], "4.7 5.6 11.4": ["warble"], "8.7 16.2 12.0": ["evolutionists"], "12.2 10.6 8.1": ["stinginess"], "7.0 -2.2 2.3": ["od"], "-3.0 1.8 -1.1": ["electrophysiology"], "17.3 8.5 11.3": ["stiffs"], "8.4 0.8 17.1": ["cheesecloth"], "18.0 14.5 4.6": ["thudded"], "1.0 10.0 13.8": ["olp"], "0.8 7.8 7.6": ["macroscopic"], "-7.3 11.5 11.8": ["concubines"], "1.3 18.0 4.6": ["revile"], "-4.6 9.6 2.1": ["grantor"], "0.2 2.8 9.1": ["ies"], "-2.3 8.2 3.7": ["retouched"], "-6.2 -1.9 16.6": ["boho"], "6.3 13.0 6.5": ["marcher"], "-3.8 8.9 0.2": ["outrushed"], "-1.3 12.1 11.9": ["outswinger"], "-6.1 -2.1 2.9": ["neonates"], "-0.2 -1.4 7.8": ["phthalate"], "12.2 5.8 11.3": ["plasterboard"], "-6.2 5.4 16.0": ["celiac"], "-3.6 -2.6 7.4": ["choline"], "16.2 5.4 5.0": ["nationalizations"], "6.5 7.6 8.2": ["underlay"], "0.0 4.4 13.5": ["sulfates"], "-4.7 -3.7 8.7": ["exonerations"], "6.8 21.7 10.1": ["conspires"], "5.4 7.2 -0.9": ["chambermaid"], "0.5 3.8 3.2": ["unrepaired"], "2.9 1.9 9.8": ["dermal"], "8.1 4.8 15.2": ["snaffled"], "6.9 -2.5 3.3": ["ebullience"], "9.7 18.4 6.2": ["deviants"], "4.3 12.6 3.4": ["linearly"], "-0.7 0.8 10.2": ["bikeway"], "5.9 15.5 4.8": ["intellects"], "13.2 7.2 13.4": ["hominid"], "-0.7 5.5 0.5": ["calibrations"], "8.2 9.4 3.5": ["bawled"], "25.0 15.4 9.6": ["levitate"], "3.2 7.0 7.5": ["flatmates", "intermittency"], "11.8 9.2 10.0": ["insomniacs"], "11.2 9.7 3.9": ["jabbering"], "8.3 14.8 11.7": ["binocular"], "5.8 0.7 39.5": ["confit"], "3.9 15.1 7.0": ["busyness"], "1.3 0.8 28.8": ["provolone"], "0.2 5.7 -0.2": ["anesthetists"], "3.6 6.0 7.7": ["anatomically"], "1.0 4.3 10.3": ["groundings"], "-8.9 8.1 9.0": ["aflatoxin"], "11.9 -4.9 9.6": ["rejigged"], "-6.1 3.4 13.5": ["ballasts"], "-0.9 7.3 11.1": ["cavers"], "3.7 -0.9 46.8": ["filets"], "7.6 6.3 1.2": ["fidget"], "1.3 -3.8 8.5": ["bedtimes"], "1.1 8.3 7.3": ["immobilization"], "4.2 3.2 10.2": ["hart"], "-3.2 5.1 6.9": ["refinish"], "4.2 22.5 7.6": ["displease"], "10.6 13.0 6.5": ["incompetents"], "1.7 12.7 8.3": ["startles"], "-11.0 5.1 5.0": ["bitrate"], "0.8 8.9 0.3": ["remediating"], "-2.8 8.2 5.9": ["evaporator"], "-1.5 -4.2 11.1": ["gms"], "6.0 7.3 25.2": ["fledglings"], "3.4 1.8 5.1": ["liraglutide"], "4.0 20.5 4.7": ["harry"], "-3.7 -1.5 16.5": ["bonspiel"], "-2.6 8.5 10.5": ["flyouts"], "-5.3 24.9 4.4": ["brutalize"], "6.0 7.6 -3.1": ["salespersons"], "0.6 5.7 6.2": ["nanocrystals"], "7.7 -4.8 3.6": ["overfilled"], "1.4 5.0 6.3": ["misstating"], "8.9 1.6 3.7": ["muss"], "-2.0 4.9 4.6": ["unescorted"], "22.5 15.5 15.6": ["plutocrats"], "3.0 4.8 9.4": ["castrate"], "-3.4 2.3 5.3": ["thinkorswim"], "-4.1 6.7 14.0": ["dolomite"], "-5.4 5.7 16.4": ["taconite"], "10.8 4.0 12.0": ["naturals"], "8.0 8.1 23.2": ["chunked"], "2.2 5.6 11.0": ["coloreds"], "1.3 6.2 3.8": ["allottees"], "16.7 5.9 41.6": ["porpoise"], "0.5 10.1 -2.0": ["imbuing"], "15.6 10.3 10.5": ["wedging"], "2.2 4.0 16.4": ["mainboard"], "17.1 10.4 23.0": ["gazelles"], "0.8 11.3 13.0": ["determinism"], "11.5 6.3 5.8": ["omg"], "7.9 7.2 11.6": ["sidewalls"], "16.3 15.4 5.6": ["inelegant"], "14.4 17.7 14.1": ["gringos"], "-7.7 9.4 9.5": ["perifosine"], "-0.6 6.5 6.8": ["radiographs"], "5.7 -0.3 8.8": ["turbotax"], "-4.6 2.2 13.2": ["tiering"], "-4.5 6.4 14.0": ["wistfulness"], "1.7 -1.4 3.5": ["rayon"], "10.9 7.8 5.0": ["creaks"], "8.4 20.9 12.2": ["otherness"], "-2.6 8.9 -0.0": ["inviolability"], "2.5 13.8 16.1": ["righthanded"], "16.7 14.7 9.7": ["astroturf"], "10.6 0.8 4.2": ["haptic"], "4.3 18.1 7.2": ["exaltation"], "-5.6 -2.5 5.0": ["pharmacovigilance"], "16.6 16.0 23.6": ["magpies"], "-3.4 22.8 12.2": ["cooldown"], "4.3 0.6 4.6": ["baler"], "3.2 4.2 3.5": ["bleat"], "0.1 20.3 12.3": ["extents"], "7.9 5.1 7.0": ["stingier"], "25.7 13.9 15.4": ["azure"], "2.5 16.5 4.8": ["hollowness"], "7.9 21.4 7.4": ["fearmongering"], "-7.2 -2.6 5.0": ["throughputs"], "5.6 13.8 15.7": ["outsides"], "0.5 7.6 -4.5": ["blunter"], "-10.0 3.4 2.7": ["catheterization"], "-2.4 1.0 0.5": ["retraces"], "28.5 23.2 16.6": ["ogres"], "1.1 8.5 11.1": ["expressionist"], "17.1 14.1 25.5": ["yucca"], "1.6 8.4 15.5": ["crampons"], "-1.3 14.4 6.7": ["missspell"], "5.9 9.2 12.4": ["abodes"], "8.2 15.9 12.3": ["nakedly"], "5.8 3.1 6.8": ["rollerblading"], "7.4 -2.7 9.2": ["tr"], "8.8 8.0 5.7": ["consolidators"], "2.7 2.1 33.6": ["frittata"], "7.4 11.2 14.5": ["artform"], "-3.6 7.9 4.3": ["undershoot"], "3.8 17.9 16.9": ["crosscourt"], "5.7 7.9 23.2": ["begonias"], "3.6 14.2 6.0": ["flybys"], "2.6 11.0 24.4": ["masa"], "8.2 11.9 9.1": ["prattle"], "2.4 8.3 9.0": ["pumpers"], "7.2 16.0 -2.7": ["repairer"], "15.1 5.2 5.7": ["oxymoronic"], "15.1 16.8 8.4": ["maniacally"], "-5.6 22.1 -3.1": ["misunderstands"], "11.0 19.8 5.6": ["unblinking"], "-2.2 9.5 4.8": ["solver"], "7.1 3.9 1.1": ["ticketless"], "20.4 8.1 11.9": ["abacus"], "3.4 2.7 3.7": ["txt"], "4.3 2.7 12.6": ["duvets"], "20.9 18.0 5.8": ["automatons"], "4.3 7.3 3.7": ["rentable"], "-5.8 14.8 5.7": ["conversationalist"], "2.0 5.2 0.7": ["overrules"], "18.0 10.9 12.1": ["pooping"], "6.6 8.7 1.5": ["overworking"], "1.1 5.5 1.6": ["kwacha"], "-8.1 4.7 7.3": ["grantmaking"], "9.1 16.1 6.5": ["craftily"], "-5.6 0.7 8.5": ["cottons"], "-9.4 4.5 10.0": ["bassists"], "0.3 10.6 6.8": ["objectification"], "9.2 24.3 7.3": ["heathens"], "6.7 3.0 17.2": ["fledged"], "6.4 -4.6 3.0": ["levs"], "-5.5 1.2 -4.4": ["neuromodulation"], "11.5 12.2 22.4": ["storks"], "0.6 5.3 35.7": ["focaccia"], "5.4 8.3 13.5": ["filesharing"], "22.8 31.5 15.6": ["droids"], "8.3 7.1 3.3": ["beguiled"], "13.1 10.3 4.0": ["refashion"], "6.9 8.6 11.8": ["yap"], "13.3 11.1 10.2": ["racketeers"], "7.9 -1.8 0.6": ["annoucement"], "3.8 1.9 12.1": ["initiations"], "6.0 1.4 21.4": ["tra"], "3.5 10.0 24.2": ["chickadees"], "7.2 -1.7 13.3": ["preshow"], "7.9 6.9 18.6": ["quill"], "4.0 13.9 1.7": ["fount"], "-6.5 1.6 -2.7": ["retweeted"], "-0.3 6.7 3.7": ["misappropriate"], "-1.0 4.7 8.6": ["afghans"], "7.4 12.0 11.1": ["musculature"], "-0.5 10.0 13.4": ["storekeeper"], "4.2 -0.2 14.5": ["acai"], "1.9 4.0 2.9": ["obligating"], "5.5 15.6 15.1": ["hardiness"], "4.7 5.6 4.3": ["reformulating"], "-9.1 1.2 -0.3": ["pastored"], "-13.3 5.7 6.3": ["internalization"], "12.4 -5.6 -1.7": ["milllion"], "-1.2 12.0 16.7": ["underbody"], "-9.1 -1.9 0.4": ["mastectomies"], "11.5 10.8 14.1": ["mandala"], "6.3 1.4 9.1": ["gatehouse"], "4.9 7.2 0.1": ["apposite"], "2.9 3.3 2.2": ["repatriations"], "4.0 11.8 10.1": ["bodyweight"], "-7.6 4.4 4.9": ["homesteaded"], "-5.6 18.1 -1.9": ["antigovernment"], "12.9 11.8 6.4": ["monopolization"], "1.7 12.8 7.1": ["impositions", "bahujan"], "2.9 -5.2 33.3": ["canneries"], "6.8 7.9 8.4": ["wich"], "0.6 7.4 7.2": ["anon"], "7.9 -2.3 4.3": ["stewarding"], "16.5 7.9 10.3": ["wtf"], "6.1 7.0 -1.5": ["recommitment"], "4.6 2.6 11.2": ["splints"], "4.6 9.4 15.0": ["forestalled"], "10.7 14.0 11.8": ["recalcitrance"], "3.0 10.0 12.2": ["subunit"], "21.2 27.6 27.4": ["earthworm"], "-6.0 -7.3 14.8": ["medicaid"], "-2.7 -0.6 3.6": ["organists"], "2.8 7.0 2.8": ["changin"], "7.3 5.3 17.3": ["gruel"], "6.1 5.8 3.7": ["glowingly"], "13.2 8.5 2.1": ["wanderers"], "6.7 0.8 11.8": ["antacid"], "12.9 3.7 9.5": ["besetting"], "-0.6 10.7 19.3": ["vacationer"], "-9.0 -0.1 7.0": ["saxophonists"], "8.2 10.1 38.2": ["mudflats"], "3.0 9.6 4.0": ["redline"], "6.7 14.5 6.3": ["egomaniacal"], "7.6 0.2 5.1": ["hav"], "5.6 8.4 4.2": ["werent"], "8.1 24.7 1.7": ["parachutists"], "1.9 18.0 9.9": ["enumerating"], "10.8 8.8 2.0": ["cupholders"], "-1.9 4.0 -3.9": ["recieving"], "2.3 10.4 6.5": ["creepier"], "13.1 3.8 9.4": ["glistened"], "6.8 5.4 0.7": ["endowing"], "-7.3 5.7 -1.0": ["condole"], "7.1 18.3 13.7": ["scowls"], "-3.9 16.4 5.8": ["preplanned"], "5.2 9.0 29.2": ["breadsticks"], "6.8 19.6 10.9": ["imprisons"], "-4.2 17.5 7.3": ["bypoll"], "1.6 16.0 1.7": ["centrism"], "11.8 12.7 15.3": ["hindquarters"], "-9.5 10.0 -0.1": ["nominator"], "15.6 7.3 8.8": ["slobs"], "14.0 9.9 10.6": ["interminably"], "4.0 -0.1 29.8": ["penne"], "2.9 28.7 5.8": ["dehumanize"], "-0.1 10.7 9.5": ["carbide"], "3.6 3.3 0.5": ["dale"], "-0.1 1.7 11.3": ["kyat"], "-5.0 6.1 12.6": ["wicketkeeping"], "13.1 -1.9 12.5": ["gummed"], "5.1 2.3 12.0": ["muralist"], "16.2 12.8 22.3": ["gullet"], "1.2 14.3 12.8": ["framerate"], "3.9 0.8 2.0": ["outdistancing"], "11.1 9.3 5.8": ["screeds"], "18.2 10.7 18.9": ["scepter"], "2.5 15.6 3.4": ["ramification"], "-2.4 5.7 13.4": ["cetuximab"], "8.6 8.0 5.1": ["stiffens"], "8.3 10.8 10.2": ["fancying"], "9.2 0.8 5.3": ["skintight"], "7.8 2.9 5.0": ["chicago"], "8.8 18.2 5.1": ["bitterest"], "-0.4 20.0 5.4": ["mateship"], "-4.2 2.4 5.9": ["redistributes"], "-1.5 10.6 13.2": ["motility"], "7.6 17.4 10.8": ["improbability"], "7.5 7.4 9.6": ["jobbers"], "1.9 8.8 24.4": ["impatiens"], "-0.2 4.3 0.7": ["tht"], "5.5 3.7 2.5": ["reworks"], "4.8 10.4 -0.3": ["overleveraged"], "5.6 10.9 6.3": ["oscillated"], "-0.6 17.3 6.6": ["humbleness"], "10.6 1.8 8.7": ["binging"], "14.3 14.9 8.6": ["sneakily"], "6.5 25.5 5.7": ["dehumanized"], "-4.4 4.5 2.6": ["pharmacologic"], "10.7 -5.0 5.8": ["ws"], "8.5 5.1 10.1": ["deluges"], "4.4 4.8 -3.2": ["especial"], "6.0 1.5 7.5": ["lanyards"], "-13.5 2.8 4.0": ["pharmacotherapy"], "4.9 2.9 9.6": ["homerless"], "4.0 0.4 9.9": ["mandals"], "-0.9 0.7 2.4": ["slating"], "1.7 -0.7 1.4": ["zines"], "16.7 0.3 3.5": ["guzzled"], "4.2 3.3 23.6": ["peony"], "-4.2 8.6 4.9": ["detoxifying"], "4.8 6.4 9.5": ["bromides"], "3.0 9.7 8.4": ["ezetimibe"], "3.7 11.2 17.8": ["greenhorn"], "-1.6 -2.9 8.0": ["deliberates"], "-1.0 11.4 1.4": ["intuitions"], "10.0 12.6 38.9": ["muskrat"], "1.6 7.1 -2.5": ["lambast"], "4.0 3.7 19.0": ["horticulturists"], "21.7 16.6 10.5": ["dartboard"], "4.5 0.9 8.4": ["rigmarole"], "14.3 10.6 14.3": ["teacups"], "-5.3 6.4 0.5": ["vitiated"], "6.6 29.0 -4.3": ["spymaster"], "-3.1 15.7 6.6": ["absconders"], "5.0 6.5 -4.7": ["rubbishing"], "8.3 23.6 11.4": ["jetpack"], "0.4 9.3 9.2": ["yourselfer"], "-3.0 15.2 10.6": ["diminishment"], "10.7 9.1 0.5": ["implausibly"], "8.7 0.7 3.8": ["professorships"], "-0.8 12.6 20.7": ["windsurfer"], "2.6 2.2 14.5": ["billfold"], "8.1 -0.4 4.6": ["drooled"], "13.2 -3.9 3.9": ["preload"], "-5.4 6.5 16.9": ["champagnes"], "7.5 9.9 -0.4": ["roofless"], "16.1 5.4 9.1": ["maracas"], "16.2 1.1 16.0": ["exotica"], "7.8 21.8 2.4": ["sabers"], "7.3 6.4 18.5": ["cottonwoods"], "5.7 7.3 4.6": ["stably"], "7.6 7.1 6.1": ["cybersquatting"], "-2.6 7.0 11.3": ["exfoliation"], "4.6 10.2 3.9": ["windowpanes"], "3.4 13.7 8.2": ["masochism"], "8.9 1.9 8.0": ["highfalutin"], "8.2 32.4 12.1": ["confederate"], "8.8 7.7 1.3": ["boxcars"], "4.6 10.3 5.4": ["godliness"], "16.9 23.6 7.2": ["searchlights"], "4.3 8.9 9.1": ["nonbank"], "-0.3 8.4 -3.3": ["statment"], "3.9 -1.0 2.6": ["biorefineries"], "2.6 14.0 19.5": ["dingoes"], "8.0 -3.1 1.2": ["greenlighted"], "10.2 15.4 10.6": ["lout"], "-0.2 28.3 3.1": ["unilateralist"], "5.8 -0.0 9.6": ["grandfatherly"], "-3.9 5.3 13.7": ["peatlands"], "3.2 6.9 13.9": ["storeowner"], "0.9 9.1 6.6": ["sagacity"], "6.2 10.5 6.4": ["transgressive"], "0.9 23.0 9.7": ["airdrop"], "8.9 12.8 5.4": ["texturing"], "3.0 22.6 6.4": ["offscreen"], "6.6 12.9 9.1": ["hypochondriac"], "-11.0 -2.3 13.1": ["broodmares"], "8.1 18.3 4.5": ["rabidly"], "12.3 2.9 10.1": ["helical"], "13.0 4.1 12.1": ["sacs"], "-2.7 11.5 -0.0": ["presumptively"], "4.9 6.2 9.9": ["ringworm"], "-1.9 3.3 4.7": ["etrials"], "-0.6 13.8 13.4": ["dulls"], "9.3 7.1 11.8": ["netizen", "voici"], "1.4 16.2 15.2": ["habitations"], "7.5 8.9 15.6": ["unpainted"], "4.3 7.9 4.1": ["talkies"], "10.3 7.0 5.4": ["accross"], "8.5 12.9 4.4": ["quandaries"], "12.9 7.2 11.2": ["sclerotic"], "4.7 12.1 13.7": ["lowlight"], "5.4 5.6 7.7": ["strums"], "-1.2 14.9 0.1": ["penetrative"], "-1.3 4.9 4.8": ["girlhood"], "2.0 7.0 3.0": ["hymnal", "extubated"], "4.2 -0.4 -2.6": ["spectrometers"], "13.9 10.0 12.1": ["treeless"], "8.7 15.3 8.3": ["toughs"], "2.0 9.7 17.1": ["paver"], "6.2 -1.6 1.9": ["fter"], "6.7 13.1 5.7": ["soundest"], "10.9 -0.3 6.0": ["trikes"], "5.2 7.0 10.6": ["virtuosos"], "1.4 6.1 4.5": ["trackable"], "4.6 -2.3 14.3": ["sugared"], "6.2 4.9 4.6": ["connote"], "12.0 11.8 -0.8": ["handbills"], "9.2 13.0 1.6": ["dialers"], "14.1 9.4 7.2": ["stupefied"], "9.3 14.8 41.7": ["mallard"], "6.5 13.4 18.0": ["goblet"], "1.7 -6.7 0.5": ["prequalified"], "-3.0 16.7 10.7": ["doxycycline"], "13.6 20.0 8.8": ["aggro"], "-2.8 4.9 2.2": ["renovates"], "-1.7 4.0 9.6": ["bulimic"], "11.6 8.8 15.7": ["chisels"], "-4.6 29.4 8.9": ["tacticians"], "-2.9 -1.4 14.1": ["insemination"], "-3.0 -3.0 16.8": ["pedicabs"], "-1.7 2.2 6.7": ["choreographs"], "-7.8 10.8 -1.2": ["enlightens"], "1.5 -1.9 2.0": ["microfiber"], "10.7 9.8 15.8": ["blastoff"], "7.6 2.3 -1.4": ["july"], "3.0 4.2 4.1": ["antacids"], "0.8 8.0 9.2": ["germinating"], "4.8 5.6 3.9": ["widescale"], "18.1 5.1 24.0": ["alabaster"], "-5.2 1.3 -1.4": ["appellees"], "19.8 20.3 1.9": ["omnipresence"], "-2.3 4.3 8.1": ["dementias"], "1.4 0.0 5.9": ["operatorship"], "11.1 3.1 6.1": ["tailwinds"], "-6.1 12.5 -1.6": ["assessable"], "6.8 4.9 0.1": ["ownerships"], "6.9 2.9 1.2": ["microsites"], "-0.0 6.2 15.0": ["immunoglobulin"], "4.6 -4.8 3.2": ["hobnobbed"], "1.2 7.2 14.6": ["rainiest"], "2.4 15.1 14.5": ["sugarcoating"], "3.5 10.9 14.9": ["backbeat"], "-3.5 3.5 6.2": ["oxaliplatin"], "11.4 14.7 11.8": ["righteously"], "9.6 13.1 10.5": ["approximations"], "7.6 9.0 5.2": ["blathering"], "4.4 -3.4 11.6": ["snips"], "15.8 17.5 23.0": ["cobras"], "3.4 5.0 10.5": ["enlivening"], "4.0 11.1 10.2": ["gloveman"], "2.6 3.2 5.9": ["silico"], "-4.4 13.5 4.2": ["gratefulness"], "5.8 0.8 7.0": ["tpa"], "-7.0 -0.6 4.5": ["rhinoplasty"], "8.7 8.3 6.2": ["archways"], "-3.3 7.1 12.1": ["downshifting"], "10.4 28.5 -1.6": ["weaponized"], "7.9 0.1 1.1": ["refillable"], "-5.5 1.7 4.4": ["alemtuzumab"], "11.8 26.4 9.1": ["invulnerability"], "-2.2 7.7 3.3": ["wakeup"], "7.2 8.2 11.3": ["windfarms"], "10.6 15.7 10.8": ["spittle"], "-1.6 5.5 19.2": ["equines"], "2.4 6.9 4.0": ["probabilistic"], "12.6 1.1 9.8": ["recoups"], "2.2 13.8 8.5": ["backdoors"], "0.5 27.7 2.8": ["jihadism"], "-1.6 13.3 7.5": ["abdominals"], "-10.6 -3.0 4.3": ["continence"], "-1.1 4.6 6.9": ["mastitis"], "4.4 0.3 13.8": ["brownstones"], "-10.3 2.2 2.7": ["remissions"], "12.0 6.6 12.2": ["gape"], "15.0 1.2 2.6": ["bwin"], "7.8 37.3 0.9": ["soliders"], "2.1 8.4 20.9": ["crocuses"], "11.2 16.9 15.2": ["pussycat"], "-5.4 1.9 8.2": ["postdoc"], "4.2 8.1 8.9": ["filename"], "0.2 5.0 1.6": ["drupa"], "-6.2 7.8 2.7": ["diverges"], "1.9 2.5 14.1": ["precast"], "6.2 11.7 6.0": ["apertures"], "-5.7 6.2 -1.7": ["deportment"], "2.3 9.2 1.0": ["kilotons"], "4.1 2.2 28.2": ["quince"], "25.1 18.3 10.1": ["gargoyles"], "6.0 8.9 5.8": ["counteracts"], "9.8 6.7 3.1": ["letterboxes"], "7.7 18.9 16.3": ["dickens"], "9.2 13.8 9.2": ["disses"], "15.7 14.5 11.0": ["nimbleness"], "-0.7 9.5 11.3": ["jawboning"], "10.3 6.6 16.3": ["hokum"], "13.3 6.8 9.6": ["pinstripe"], "2.8 7.1 8.5": ["intercooler"], "16.9 -0.1 16.1": ["parasols"], "15.9 23.1 27.8": ["cannonballs"], "10.3 5.8 5.2": ["conflation"], "-9.0 16.3 3.8": ["exigency"], "-0.8 19.4 14.8": ["nativist"], "6.4 10.1 1.5": ["retarding"], "1.4 5.8 2.6": ["kilobytes"], "-3.8 2.1 0.8": ["supercede"], "0.8 -0.7 1.5": ["televises"], "-3.8 5.7 20.1": ["woodstove"], "23.1 4.4 21.0": ["jointed"], "-9.2 -0.3 -3.9": ["editorship"], "3.6 0.0 15.0": ["molar"], "10.1 -1.9 21.4": ["scalloped"], "6.3 5.6 3.9": ["withthe"], "6.4 0.3 7.6": ["outdueling"], "0.2 13.5 12.4": ["fibbing"], "-5.3 8.6 5.3": ["teleworkers"], "0.7 -2.3 0.5": ["enlargements"], "0.2 4.9 7.5": ["sadhus"], "3.5 6.3 2.9": ["ducting"], "-1.0 11.1 31.4": ["riprap"], "4.1 9.0 2.9": ["phonetically"], "-1.3 9.6 -2.2": ["comportment"], "4.7 6.2 6.9": ["backroads"], "11.9 4.4 17.9": ["sycamore"], "1.9 -0.1 -4.6": ["legibility"], "11.2 8.1 15.7": ["dlr"], "17.4 16.1 8.6": ["creepiest"], "5.2 5.6 14.5": ["petit"], "1.6 15.5 14.1": ["scrummage"], "12.6 16.1 13.4": ["deadening"], "2.5 -0.6 -0.3": ["validations"], "4.0 16.7 5.1": ["evaders"], "-5.0 6.8 2.6": ["deltathree"], "-5.0 6.8 12.7": ["ratables"], "11.8 1.9 8.4": ["crinkled"], "14.0 26.7 3.1": ["teleportation"], "0.6 27.5 5.3": ["confederates"], "-3.3 9.4 1.4": ["runningback"], "6.0 6.2 8.9": ["tediously"], "-8.7 8.5 5.8": ["withholdings"], "8.4 12.5 10.7": ["doughty"], "-4.7 2.9 29.1": ["capsicum"], "5.7 12.4 12.3": ["fife"], "5.3 12.7 1.0": ["perspiring", "lukewarmly"], "3.5 9.7 16.4": ["braai"], "14.8 33.6 10.6": ["supervillain"], "-8.8 3.5 1.7": ["kirpan"], "19.1 9.4 25.2": ["porcupines"], "-4.9 13.4 7.2": ["jumpshot"], "2.9 5.2 7.9": ["mineralogy"], "8.2 19.4 3.7": ["agitprop"], "10.5 13.5 6.1": ["skulduggery"], "3.9 -0.1 4.8": ["hydrologists"], "3.4 8.0 8.7": ["futbol"], "0.9 -2.5 13.8": ["cycleway"], "-2.1 0.0 2.6": ["tem"], "7.2 4.4 11.3": ["reordered"], "-11.4 -6.8 6.8": ["trimesters"], "3.9 6.4 4.6": ["rerelease"], "6.9 18.1 4.9": ["secreting"], "9.0 15.4 13.6": ["swashbuckler"], "1.7 21.4 3.3": ["consorting"], "9.4 12.0 26.8": ["nettles"], "-10.2 0.5 0.2": ["reappointing"], "2.6 0.1 -3.5": ["spokeman"], "-1.3 5.5 10.2": ["habitability"], "-1.3 4.6 -2.1": ["lightheadedness"], "2.4 11.3 28.7": ["mulberry"], "0.1 -2.8 39.2": ["oystermen"], "-4.1 20.3 5.7": ["extrajudicial"], "-2.0 8.9 11.0": ["matatu"], "3.3 5.0 1.3": ["recaptures"], "17.5 10.2 14.0": ["haunches"], "8.4 17.3 -6.3": ["bombards"], "20.0 11.5 18.3": ["imp"], "6.0 18.4 6.1": ["breakable"], "1.0 5.5 4.9": ["uninstalled"], "9.0 15.9 5.2": ["restlessly"], "13.9 6.1 14.9": ["dimple"], "5.8 5.5 12.1": ["smalls"], "-11.0 4.1 1.8": ["belimumab"], "-5.2 -1.3 10.3": ["reinstituted"], "-6.6 6.5 -1.5": ["myocardial"], "3.0 7.1 9.9": ["woofer"], "6.4 11.0 24.9": ["conifer"], "-4.7 -1.7 2.1": ["tf"], "7.2 14.6 6.5": ["seethes"], "13.7 7.5 7.4": ["cineplex"], "15.5 6.4 10.8": ["tombola"], "-16.2 5.0 14.4": ["mgd"], "20.5 2.4 19.3": ["glisten"], "0.5 14.1 0.6": ["reentering"], "0.2 0.7 17.0": ["siya"], "7.8 7.9 4.6": ["abdomens"], "5.9 -4.7 8.2": ["yurts"], "14.4 9.8 16.2": ["desiccated"], "6.3 2.6 13.4": ["spacers"], "-8.6 17.4 8.9": ["reelect"], "14.0 10.6 19.9": ["riggers"], "-0.6 -1.4 2.5": ["funkier"], "3.1 10.0 3.2": ["reproached"], "0.8 5.9 6.2": ["coalfield"], "-2.4 -0.6 2.4": ["bioethicist"], "13.8 17.2 7.9": ["stealer"], "4.3 9.4 12.0": ["lading"], "-5.8 15.8 6.8": ["bypolls"], "8.7 11.8 15.2": ["shinny"], "2.5 12.5 1.5": ["favela"], "8.4 13.8 10.4": ["irritatingly"], "11.4 -0.2 8.8": ["velor"], "2.4 3.6 -0.6": ["reinvigoration"], "9.5 23.4 17.2": ["motherfucker"], "3.8 5.3 15.9": ["pectoral"], "0.1 3.7 1.5": ["hanker"], "10.9 20.8 6.3": ["enfeebled"], "18.4 5.5 17.4": ["slathering"], "5.6 11.1 20.6": ["bougainvillea"], "-3.1 -1.4 7.1": ["streetscaping"], "10.6 -0.8 3.0": ["showgrounds"], "19.1 13.9 10.5": ["pixilated"], "2.7 4.1 -3.9": ["crusaded"], "5.6 -1.3 3.7": ["concierges"], "-1.4 6.5 2.3": ["underplaying"], "7.6 9.9 9.0": ["timpani"], "-0.8 6.4 18.5": ["tartness"], "6.2 9.2 14.9": ["labrador"], "1.2 -1.6 8.5": ["raunch"], "1.5 19.1 2.2": ["unlearn"], "7.5 3.1 2.8": ["bis"], "-2.0 2.9 11.3": ["niya"], "-2.3 28.4 10.9": ["gunnery"], "7.1 5.0 21.7": ["dun"], "-6.8 8.7 3.1": ["dehumidifier"], "1.7 12.9 6.2": ["tactless"], "9.0 8.7 13.6": ["bluer"], "8.4 13.9 9.5": ["truisms"], "0.9 6.2 4.5": ["pulsars"], "-2.3 2.7 7.7": ["undergarment"], "-3.2 1.5 9.7": ["maybes"], "19.5 26.6 13.9": ["periscope"], "3.2 16.1 4.1": ["amputating"], "-3.1 3.5 12.1": ["ghat"], "13.2 27.8 14.6": ["looter"], "7.4 6.8 6.9": ["sharemarkets"], "-1.8 22.8 1.9": ["revisionists"], "7.8 7.1 4.3": ["hertz"], "12.4 18.6 2.7": ["imitator"], "-4.8 2.5 -3.7": ["neuroprotective"], "12.6 3.4 7.6": ["reignites"], "5.4 7.2 7.3": ["intercut"], "9.1 11.9 8.3": ["fickleness"], "5.2 7.5 4.6": ["bowser"], "13.9 9.6 33.5": ["urchins"], "10.1 5.5 11.6": ["lotta"], "2.8 12.1 8.5": ["predilections"], "-2.4 16.4 2.5": ["misconstrue"], "-8.2 0.6 -1.6": ["contraindications"], "2.3 9.8 11.8": ["joyriding"], "5.0 5.0 6.8": ["shopaholic"], "8.7 10.7 22.1": ["serrated"], "18.7 15.8 0.2": ["snoops"], "5.9 3.8 6.7": ["storeyed"], "2.3 3.5 4.8": ["imagers"], "15.2 28.0 9.8": ["lairs"], "-2.2 14.5 4.0": ["intellectualism"], "8.4 17.5 24.8": ["hemlocks"], "12.6 8.5 6.2": ["whew"], "1.0 17.6 8.8": ["overcompensate"], "-0.3 3.3 0.9": ["reinjuring"], "15.2 3.9 4.6": ["fistfuls"], "7.9 9.8 8.6": ["rivulets"], "-10.8 5.2 -3.9": ["belabor"], "4.7 3.2 5.7": ["pyrolysis"], "-14.6 19.0 1.3": ["debriefings"], "3.2 15.4 0.1": ["peons"], "14.8 15.6 32.6": ["deliciousness"], "-0.6 1.5 12.2": ["gasoil"], "4.9 5.9 -3.5": ["receptiveness"], "-3.1 -1.4 2.1": ["prostituting", "enge"], "22.3 10.3 18.0": ["lemming"], "3.7 -1.9 14.6": ["safflower"], "11.4 -1.1 -0.3": ["tp"], "9.0 7.3 8.2": ["hicks"], "2.0 5.6 3.9": ["ritonavir"], "5.2 14.7 13.1": ["hardiest"], "0.2 -3.0 5.9": ["microgram"], "10.6 23.9 9.4": ["warps"], "2.7 11.5 10.0": ["unhealthful"], "6.1 -0.1 3.4": ["adhoc"], "1.0 7.8 33.3": ["shallot"], "2.7 12.6 -0.5": ["faithfuls"], "14.7 2.3 14.0": ["mexican"], "-5.2 5.4 11.0": ["filmi"], "4.8 11.2 21.4": ["lakers"], "1.7 5.7 15.7": ["woodworkers"], "0.8 11.8 10.2": ["portage"], "6.8 15.8 5.6": ["keyloggers"], "8.3 -1.5 9.7": ["baling"], "17.7 5.7 18.1": ["corpulent"], "4.7 17.8 9.1": ["eff"], "12.8 -5.5 0.6": ["atthe"], "0.2 11.5 6.6": ["depressant"], "-0.0 18.8 10.0": ["monarchists"], "5.3 18.7 7.4": ["carpetbagger"], "10.1 14.3 10.9": ["flamboyantly"], "1.8 11.7 5.5": ["reframing"], "9.6 11.2 30.6": ["chrysanthemum"], "5.2 14.7 7.7": ["untalented"], "6.8 11.3 5.7": ["gesticulating"], "12.6 16.8 10.5": ["guileless"], "10.5 3.1 12.2": ["animatedly"], "5.7 7.3 3.5": ["ginned"], "4.2 3.9 10.1": ["handymen"], "9.1 3.6 29.9": ["suet"], "3.1 11.8 23.7": ["pronghorn"], "6.6 19.2 9.0": ["softy"], "5.4 5.1 16.8": ["cuticle"], "28.3 15.4 23.4": ["mousetrap"], "2.8 9.3 5.8": ["quackery"], "7.6 -2.2 6.2": ["january"], "-1.8 17.2 9.3": ["denuclearize"], "-4.4 2.2 9.1": ["biochar"], "10.6 6.4 20.6": ["noshing"], "14.1 0.1 5.5": ["ream"], "12.8 9.6 11.8": ["murk"], "12.9 13.1 19.9": ["mallets"], "-2.3 1.5 4.4": ["republishing"], "23.8 2.2 14.1": ["pinwheel"], "7.6 10.5 11.9": ["senility"], "2.4 8.6 5.4": ["dilettante"], "-6.4 -3.9 -2.3": ["prescreened"], "11.3 17.7 7.6": ["creepily"], "6.2 4.9 22.3": ["candied"], "4.4 2.3 9.7": ["houseful"], "10.0 19.0 12.4": ["alchemist"], "7.8 15.1 14.3": ["chokeslam"], "4.3 -8.9 2.6": ["smartcards"], "-9.9 -3.5 -7.7": ["cardiopulmonary"], "6.5 23.7 9.3": ["ingratitude"], "3.5 12.5 5.9": ["retype"], "8.8 10.8 30.6": ["cetaceans"], "-11.1 -7.7 1.2": ["remanding"], "-4.5 10.7 13.1": ["hardcovers"], "1.3 0.1 7.1": ["volcanologist"], "9.3 4.2 17.1": ["amethyst"], "4.2 2.5 8.6": ["fugue"], "-0.2 3.5 21.4": ["bushmeat"], "7.5 13.8 11.5": ["ruckmen"], "4.7 2.6 22.9": ["coir"], "7.0 14.2 9.2": ["backwash"], "6.8 6.2 1.7": ["seismically"], "13.2 12.6 0.9": ["ecstatically"], "4.1 8.6 8.6": ["stupider"], "-1.3 5.0 7.8": ["networth"], "-0.4 8.2 0.5": ["transferee"], "3.6 34.3 2.8": ["subversives"], "5.1 7.4 0.6": ["sideswipe"], "0.3 1.0 13.3": ["sked"], "15.5 3.1 6.6": ["futurists"], "9.5 4.3 3.6": ["videoed"], "2.6 12.8 3.7": ["rearward"], "-6.5 0.1 3.9": ["circulator"], "5.7 8.2 13.1": ["phlegmatic"], "9.0 28.8 8.1": ["geostrategic"], "-2.9 36.1 -3.5": ["persecutors"], "11.4 16.2 15.3": ["dumpers"], "0.8 14.1 4.3": ["clubface"], "15.6 5.0 18.8": ["scarfing"], "22.3 8.9 24.3": ["seashell"], "-1.7 15.1 3.7": ["moralists"], "-3.0 16.4 4.2": ["cinematically"], "-5.4 7.0 0.1": ["ohms"], "25.3 11.9 15.4": ["scape"], "-1.5 10.1 4.9": ["agriculturally", "moshavim"], "11.9 14.7 25.5": ["knuckler"], "2.1 1.7 7.4": ["predominated"], "-10.4 9.6 1.7": ["disputable"], "-5.6 1.8 1.6": ["novellas"], "3.4 19.7 4.1": ["unwaveringly"], "5.4 3.1 10.6": ["fiestas"], "6.2 1.4 20.4": ["mahjong"], "2.1 7.2 21.2": ["beaching"], "-5.2 5.7 4.0": ["transferability"], "-4.5 0.1 1.9": ["homologation"], "17.5 6.8 27.9": ["wiener"], "-0.7 1.0 7.3": ["epithelial"], "2.1 3.2 15.0": ["sarongs"], "4.1 6.2 3.3": ["polymeric"], "15.5 9.9 7.9": ["dazzlingly"], "7.0 15.5 8.2": ["ze"], "6.2 16.2 9.0": ["reddened"], "7.5 3.4 16.6": ["cpu"], "4.6 1.7 3.3": ["unlined"], "9.2 4.6 3.7": ["tyro"], "-11.1 9.6 2.1": ["mils"], "19.2 19.3 13.1": ["dicks"], "-13.3 13.8 10.8": ["preflop"], "6.9 6.7 8.8": ["stockroom"], "2.8 6.5 5.5": ["minibar"], "13.8 8.3 17.9": ["pong"], "0.0 24.5 2.0": ["triangulate"], "-4.9 16.4 7.3": ["editorializing"], "0.9 10.0 6.3": ["unsighted"], "5.3 15.4 9.2": ["inclement"], "1.8 5.4 6.7": ["infarction"], "4.6 1.8 12.1": ["plaids"], "8.9 11.4 0.6": ["orderlies"], "-0.3 7.2 17.3": ["backsplash"], "-5.4 10.8 0.8": ["equalizers"], "2.2 12.5 11.5": ["liverpool"], "12.7 11.2 6.7": ["videoboard"], "0.2 -3.1 12.9": ["ann"], "-13.4 12.3 0.7": ["anticoagulants"], "13.7 5.0 6.7": ["gleams"], "5.8 10.8 3.3": ["overreliance"], "3.6 11.5 9.1": ["handballs"], "6.7 6.4 7.8": ["fluster"], "-2.6 16.3 0.9": ["kindnesses"], "10.1 4.0 6.4": ["carillon"], "1.5 -0.7 6.3": ["hooping"], "-2.9 13.2 0.5": ["forensically"], "26.0 8.3 13.7": ["levitating"], "8.1 0.7 12.8": ["tollbooths"], "2.5 1.2 10.9": ["strappy"], "1.7 4.6 -0.8": ["titration"], "10.3 15.5 12.1": ["thyself"], "3.6 1.4 2.7": ["bassinets"], "5.0 9.1 12.9": ["yelped"], "10.2 9.7 12.7": ["shite"], "5.8 -3.8 -1.6": ["snappier"], "12.2 1.9 -1.3": ["nonexclusive"], "11.7 7.6 9.1": ["plaintively"], "4.8 -0.4 13.8": ["truncate"], "7.7 12.1 14.3": ["cantina"], "11.2 15.4 17.0": ["agape"], "8.1 3.1 8.1": ["tensile"], "-3.0 11.3 5.8": ["naturalness"], "-10.0 14.2 9.3": ["enlistments"], "1.2 9.8 7.7": ["offspinner"], "-10.5 0.3 -0.5": ["suicidality"], "11.9 -3.7 8.4": ["ultrathin"], "3.9 8.2 14.5": ["predominates"], "-6.0 8.8 10.2": ["upazilas"], "7.9 12.0 3.5": ["hypocrisies"], "8.3 12.8 26.8": ["lichens"], "0.4 9.6 8.6": ["repertoires"], "2.5 5.8 1.7": ["meriting"], "7.8 5.1 2.2": ["contrivances"], "7.2 11.1 9.7": ["overstressed"], "13.4 3.4 3.0": ["scoots"], "1.6 11.2 9.1": ["paraglider"], "-0.8 10.6 8.8": ["emotionalism"], "2.5 3.4 2.9": ["unamortized"], "3.1 12.9 29.5": ["biryani"], "1.3 11.5 4.8": ["misapprehension"], "9.3 10.0 3.7": ["supercharge"], "6.3 1.8 -0.1": ["geeked"], "0.8 3.8 8.5": ["durbar"], "5.3 14.5 12.4": ["gayness"], "18.4 6.7 10.7": ["bazillion"], "5.0 -1.8 9.4": ["fe"], "7.9 6.9 4.1": ["subassemblies"], "1.2 18.3 -1.5": ["evangelicalism"], "-7.2 6.9 5.1": ["defeasance"], "9.4 4.0 4.9": ["flashcards"], "6.8 17.5 7.0": ["teabaggers"], "5.3 15.7 1.9": ["sleepwalk"], "-4.0 11.5 5.5": ["misspoken"], "8.8 11.9 5.8": ["pyre"], "-10.9 7.2 -1.8": ["driveability"], "11.6 11.4 3.5": ["grimmest"], "7.4 12.9 9.7": ["loveless"], "13.8 8.5 -2.1": ["unshackled"], "9.3 14.5 11.7": ["whitest"], "8.3 23.2 9.4": ["globalist", "heareth"], "11.1 5.1 5.2": ["swaggered"], "12.8 6.6 13.8": ["flattest"], "5.9 7.8 7.3": ["silicosis"], "3.3 6.7 17.1": ["fleeces"], "-6.7 -4.1 21.9": ["cwt"], "6.8 17.0 23.1": ["crabgrass"], "10.0 21.7 6.3": ["niggers"], "-2.0 4.2 3.2": ["mellowing"], "0.6 15.5 12.9": ["rucking"], "10.9 12.4 6.1": ["disconcertingly"], "-2.4 11.3 2.8": ["incompetency"], "6.8 8.0 14.9": ["nana"], "0.5 0.2 21.2": ["challah"], "5.5 11.8 3.4": ["shabbily"], "9.5 7.5 1.8": ["brainwave"], "0.6 4.2 0.1": ["webchat"], "11.7 8.5 -1.5": ["ebitda"], "6.1 8.4 7.8": ["iso"], "14.7 6.3 22.7": ["mitten"], "3.0 5.6 3.7": ["mawkish"], "6.1 6.8 8.8": ["mkts"], "2.0 7.3 10.0": ["mien"], "9.3 12.1 7.4": ["evisceration"], "-9.2 5.4 11.5": ["trifectas", "assemblyperson"], "15.6 13.2 13.4": ["pinhead"], "6.0 5.6 3.5": ["att"], "-0.9 11.9 18.6": ["garnishment"], "3.0 2.8 20.4": ["parang"], "8.9 12.8 8.2": ["shakily"], "-7.7 6.3 4.4": ["schooldays"], "4.0 6.7 8.0": ["unambitious"], "-0.7 2.1 11.5": ["waveguide"], "-3.6 4.6 3.0": ["maturely"], "-1.6 4.5 3.9": ["hewed"], "4.8 1.1 6.7": ["ek"], "5.2 16.7 12.5": ["colonials"], "11.1 19.2 10.9": ["experimenter"], "9.5 0.7 1.9": ["amping"], "10.1 3.4 6.8": ["unzip"], "6.2 -3.1 -1.6": ["commitee"], "8.7 4.6 9.2": ["sensationalistic"], "4.8 13.6 24.9": ["boatman"], "-4.7 1.5 5.9": ["bankcard"], "-5.3 15.2 -4.9": ["radicalizing"], "-6.2 4.5 14.0": ["nonwhites"], "-12.8 3.5 3.1": ["reinvestigation"], "7.1 -2.9 17.8": ["vert"], "9.5 4.6 11.7": ["shirted"], "0.8 13.6 5.7": ["lawyerly"], "-3.9 10.0 4.8": ["accountholders"], "-9.0 2.0 8.4": ["guesting"], "5.9 17.4 15.5": ["truthiness"], "-0.6 1.3 22.4": ["creaminess"], "-5.0 9.7 10.2": ["knitter"], "8.3 -3.3 7.5": ["peters"], "-3.7 10.2 5.8": ["leukemias"], "-2.8 9.3 15.0": ["agreeably"], "6.4 9.2 34.1": ["woodcock"], "-0.8 8.4 24.3": ["groins"], "1.3 8.8 3.6": ["scuffing"], "-0.8 3.2 3.3": ["assignable"], "10.9 15.9 12.6": ["recoiling"], "-1.8 9.7 5.8": ["hauntings"], "8.4 1.9 0.9": ["december"], "-4.9 8.5 7.7": ["windier"], "5.9 6.4 6.6": ["nearsighted"], "-9.3 3.8 -0.1": ["mmcf"], "16.8 25.1 4.1": ["nuked"], "8.5 7.7 12.3": ["baba"], "11.5 13.4 2.6": ["robotically"], "10.0 3.0 7.2": ["usb"], "9.5 14.7 5.2": ["mesmerize"], "7.0 10.2 12.8": ["dreidel"], "-5.1 12.5 -2.2": ["ostracize"], "-8.1 6.9 7.9": ["brainstem"], "-5.6 3.4 10.3": ["permaculture"], "10.5 14.9 2.3": ["superimpose"], "4.4 11.4 9.3": ["swelter"], "8.3 12.3 11.4": ["kneecaps"], "-0.2 -1.2 13.1": ["taillight"], "-2.3 17.9 4.0": ["soulmates"], "18.8 -2.4 5.8": ["aflutter"], "9.8 2.2 25.7": ["fondant"], "-1.5 3.1 11.9": ["couplets"], "8.9 5.3 4.0": ["bookworms"], "-2.6 4.5 3.4": ["prediabetes"], "-14.2 10.3 -1.9": ["afterword"], "10.3 -2.0 2.3": ["feelgood"], "-4.4 0.4 5.0": ["transcriptional"], "11.1 10.3 6.8": ["scything"], "-0.9 19.3 3.1": ["mischaracterization"], "-1.4 5.5 5.6": ["shaders"], "19.9 0.9 15.3": ["sunburst"], "-1.4 11.7 -0.1": ["maintainer"], "4.9 -1.7 11.2": ["ew"], "-3.4 5.0 18.5": ["stache"], "7.1 6.5 11.9": ["upcourt"], "4.8 7.6 8.3": ["explainable"], "5.6 8.5 10.4": ["trimmers"], "-1.5 23.7 0.9": ["antidemocratic"], "5.0 13.4 16.2": ["platitude"], "-4.7 3.1 16.3": ["tequilas"], "4.0 14.3 3.2": ["excercise"], "2.2 18.6 -2.3": ["antigay"], "-10.1 -1.0 9.0": ["cytology"], "11.2 6.4 10.9": ["lugubrious"], "8.1 1.6 11.5": ["bandshell"], "13.3 10.8 3.8": ["kickstand"], "-5.7 4.0 6.3": ["multicasting"], "-5.4 6.2 12.6": ["overexpression"], "3.0 10.1 4.8": ["retransmitted"], "12.7 9.5 -0.1": ["sniffers"], "7.5 12.0 7.0": ["taoiseach"], "4.4 16.4 -0.6": ["worthlessness"], "1.6 4.0 5.9": ["jeez"], "2.3 5.5 -1.9": ["unbeknown"], "2.6 11.2 9.8": ["glutes"], "11.8 13.0 5.4": ["schoolyards"], "-1.1 7.1 22.3": ["mortalities"], "7.5 5.3 1.9": ["deregulatory"], "-6.4 6.6 7.3": ["oxidative"], "10.5 4.1 0.6": ["ths"], "6.6 12.8 16.4": ["windowsills"], "12.6 8.2 6.1": ["swami"], "-1.1 -0.9 3.0": ["rebated"], "-9.6 4.2 3.0": ["cesarean"], "4.8 8.1 9.7": ["td"], "-1.6 0.8 7.4": ["orthotic"], "1.4 10.9 0.6": ["oversimplify"], "3.7 10.0 15.5": ["natal"], "2.9 19.0 13.1": ["hoons"], "17.0 16.3 18.2": ["hag"], "-3.4 8.7 19.1": ["siltation"], "13.4 8.0 16.2": ["slimed"], "-5.4 6.7 6.9": ["copywriters"], "6.9 8.7 11.5": ["bafflement"], "9.2 3.9 1.5": ["millenium"], "10.5 16.4 14.4": ["martian"], "9.2 5.4 16.6": ["thrush"], "7.0 10.3 5.1": ["memorializes"], "6.3 -7.8 1.3": ["scatological"], "10.3 14.7 17.9": ["carrion"], "10.3 16.9 6.6": ["sims"], "-4.3 10.0 2.6": ["subrogation"], "-1.7 3.1 -3.0": ["outdistance"], "3.1 8.5 5.7": ["aqueducts"], "-0.7 23.4 3.2": ["disorient"], "-1.1 3.7 14.2": ["biodynamic"], "-2.1 7.1 13.3": ["nimotuzumab"], "7.4 1.3 13.3": ["noh"], "-1.7 -7.3 -0.9": ["shunts"], "-0.9 19.2 2.8": ["unquestioningly"], "7.1 8.9 0.5": ["aerodynamically"], "10.0 9.8 9.9": ["benders"], "-0.9 8.9 20.1": ["sanders"], "-1.0 8.2 7.1": ["insula"], "4.8 7.4 8.9": ["woebegone"], "0.2 9.6 3.6": ["devaluations"], "11.8 18.3 4.7": ["nutters"], "10.9 7.1 11.5": ["bowtie"], "-3.1 5.3 7.0": ["decriminalizing"], "-1.9 17.3 3.5": ["untrusted"], "2.3 15.1 2.9": ["problematical"], "9.3 6.5 0.3": ["pipedream"], "-10.2 8.8 4.5": ["prescriber"], "14.2 9.8 2.1": ["photorealistic"], "-7.2 13.1 8.6": ["improviser"], "-0.1 14.6 7.0": ["shariah"], "7.1 10.7 30.6": ["shuck"], "-9.2 8.2 0.5": ["enforcements"], "11.0 17.3 3.0": ["wold"], "18.3 12.4 10.9": ["cupid"], "14.4 4.4 19.4": ["sideboards"], "8.5 0.3 8.1": ["biotechnological"], "-1.7 16.4 2.1": ["firebreaks"], "6.7 3.1 7.2": ["willl"], "6.4 9.7 13.6": ["sconces"], "20.2 16.7 5.8": ["slayed"], "2.4 7.3 5.6": ["grippy"], "5.9 8.2 5.9": ["bespeaks"], "-1.5 35.5 18.0": ["mage"], "8.2 -4.7 11.5": ["barrow"], "5.9 20.2 7.1": ["supplication"], "3.2 6.2 10.3": ["lysine"], "2.7 4.1 19.9": ["ramekins"], "23.6 23.9 12.0": ["automaton"], "15.9 5.8 6.1": ["plasters"], "-1.6 15.3 11.0": ["phytonutrients"], "14.2 19.4 13.2": ["gladiatorial"], "22.2 -0.4 3.1": ["bendable"], "-3.7 9.7 11.2": ["autophagy"], "10.2 3.8 7.9": ["yammering"], "4.8 3.6 18.5": ["corsage", "threemonths"], "-6.5 0.8 -2.6": ["liaised"], "8.1 7.6 11.4": ["wordsmiths"], "-1.4 8.0 9.9": ["waterlines"], "-1.1 11.7 7.1": ["vaulter"], "2.0 3.2 29.2": ["crostini"], "19.5 0.9 14.8": ["squiggles"], "-0.3 19.1 7.9": ["brokenness"], "4.8 0.7 11.8": ["mer"], "5.8 15.7 5.4": ["islamic"], "-6.6 7.6 4.7": ["probationer"], "2.2 11.7 13.8": ["apportioning"], "0.5 8.2 4.2": ["heartbreakers"], "9.5 -1.4 5.6": ["masseuses"], "0.8 2.7 1.6": ["evince"], "7.9 6.6 53.8": ["dogfish"], "3.9 6.8 10.2": ["nanomaterial"], "-0.0 17.8 2.6": ["nobler"], "6.9 13.3 5.1": ["radiometric"], "14.8 24.7 3.0": ["abominations"], "-9.4 4.0 0.4": ["toolsets"], "-6.7 2.0 4.4": ["lenalidomide"], "10.3 7.6 10.8": ["sultans"], "19.4 27.1 9.1": ["camouflaging"], "4.9 2.2 5.7": ["jan"], "9.8 4.1 6.1": ["riyal"], "11.5 12.1 19.1": ["undersides"], "-3.3 4.7 7.3": ["veganism"], "8.3 4.7 9.7": ["coeds"], "3.5 16.2 3.4": ["serfdom"], "-3.7 8.5 1.3": ["exerciser"], "1.9 10.2 17.6": ["cosplay"], "18.2 23.6 11.4": ["pulverize"], "4.5 9.2 -2.2": ["outnumbers"], "10.5 10.9 5.2": ["cantering"], "8.2 10.7 15.5": ["whipsaw"], "6.7 -0.8 8.4": ["cafetorium"], "-15.1 -3.8 0.1": ["ebrary"], "3.4 9.9 13.6": ["snowblowers"], "-3.2 -1.1 21.3": ["pulpwood"], "-1.4 -1.8 5.1": ["bicultural"], "7.4 15.9 5.2": ["indigenously"], "5.3 3.6 11.5": ["october"], "-3.4 14.8 8.2": ["movant"], "5.3 6.0 3.6": ["cosmological"], "6.5 32.6 9.0": ["machinegun"], "5.6 8.9 11.4": ["shifters"], "-0.8 11.3 4.9": ["generalizing"], "-0.2 20.4 2.9": ["personage"], "6.3 4.8 25.0": ["heartier"], "4.2 11.0 28.5": ["monofilament"], "10.8 5.0 3.6": ["bungles"], "-0.9 2.3 -1.4": ["unswayed"], "8.7 6.5 9.9": ["leaches", "resinous"], "8.2 3.7 25.2": ["kai"], "0.8 3.1 1.0": ["cantonal"], "-9.4 5.6 5.6": ["waterflood"], "17.6 9.2 16.3": ["writhe"], "-8.1 -9.8 14.4": ["homestay"], "-1.5 10.7 9.2": ["cartographic"], "0.9 3.4 -0.9": ["miscarry"], "4.2 2.8 -1.1": ["specialism"], "6.7 4.0 3.6": ["ds"], "5.6 11.9 20.8": ["tollbooth"], "-12.5 3.5 14.7": ["dayrates"], "8.0 -0.6 2.2": ["jumpstarting"], "4.4 5.9 5.5": ["tailgated"], "-1.1 -10.1 5.8": ["whitepapers"], "5.0 11.8 4.8": ["misplays"], "13.5 7.9 21.2": ["purplish"], "10.9 14.4 1.8": ["existance"], "-5.4 3.7 13.0": ["androgens"], "14.9 10.0 12.6": ["plops"], "7.5 21.1 7.9": ["stockade"], "15.0 10.6 15.7": ["knockers"], "-5.9 19.4 -0.6": ["absconder"], "12.3 5.9 7.0": ["offshored"], "-5.5 7.5 12.1": ["widowhood"], "15.7 -5.8 2.0": ["millon"], "7.8 2.3 12.0": ["entre"], "4.6 8.4 -3.7": ["peeped"], "13.3 23.1 13.2": ["smite"], "5.6 5.2 -0.2": ["hte"], "1.5 10.4 6.6": ["sainted"], "8.0 6.6 -1.9": ["readouts"], "-1.0 8.1 6.2": ["atonal"], "-5.6 -1.5 5.8": ["rehydration"], "2.5 12.4 -2.0": ["distributive"], "6.4 13.1 7.3": ["bootlegger"], "8.3 11.2 17.6": ["dames"], "2.4 4.6 -2.0": ["impinges"], "5.7 -3.4 11.9": ["chen"], "6.3 11.1 4.4": ["ghettoes"], "-1.4 10.3 14.3": ["watercourse"], "3.8 8.6 5.8": ["executables"], "18.0 4.7 16.9": ["meerkats"], "11.9 25.9 6.5": ["bestial"], "20.8 20.2 10.7": ["corporatism"], "-3.2 2.3 9.3": ["uveitis"], "18.3 12.1 25.2": ["icebox"], "12.5 13.7 3.6": ["communing", "visualisations"], "-6.0 17.2 4.6": ["misquote"], "2.2 14.6 7.0": ["clubhead"], "3.1 -1.7 40.2": ["fishmeal"], "6.1 5.4 7.4": ["anther"], "-2.2 10.9 11.4": ["vocalize"], "-2.3 -2.3 4.8": ["softcover"], "2.9 9.2 4.1": ["sunstroke"], "8.3 6.3 23.7": ["seagoing"], "-1.8 10.5 5.8": ["interjecting"], "1.7 28.6 -4.1": ["slanders"], "-2.7 -3.6 12.6": ["sundress"], "-1.7 12.1 11.7": ["ejaculate"], "13.8 2.1 3.9": ["teem"], "-5.3 5.7 12.4": ["mandis"], "1.7 9.1 2.1": ["metroplex"], "1.7 4.5 -5.4": ["outpointing"], "5.7 8.0 12.1": ["terracing"], "10.1 0.6 6.1": ["bricklayers"], "12.3 3.1 6.6": ["tantalized"], "6.0 2.4 -3.5": ["independant"], "8.0 15.3 8.7": ["ricochets"], "17.4 15.6 10.8": ["labyrinths"], "15.0 3.2 5.0": ["overinflated"], "15.0 5.3 3.9": ["spluttered"], "3.3 5.8 7.5": ["centavo"], "7.5 7.0 8.6": ["lathes"], "15.7 0.1 6.7": ["chock", "includng"], "1.0 4.8 6.5": ["temporally"], "2.6 7.7 47.6": ["lingcod"], "16.1 6.5 1.5": ["unsourced"], "23.7 3.5 15.4": ["waddled"], "-3.1 25.1 4.6": ["counterrevolutionary"], "0.7 1.4 6.9": ["pituitary"], "20.6 -3.1 10.5": ["ornamented"], "2.2 6.9 11.0": ["config"], "-0.4 5.3 0.9": ["interlocks"], "-4.0 14.0 0.0": ["deviance"], "-2.1 12.8 9.9": ["ribosomes"], "12.5 19.1 2.9": ["obliterates"], "-0.5 12.4 13.3": ["washcloth"], "-4.5 5.0 8.6": ["episcopal"], "15.0 28.5 11.1": ["outsmarting"], "1.6 -0.0 3.0": ["upgraders"], "9.5 7.9 13.1": ["soothsayers"], "14.5 13.3 16.9": ["beefcake"], "6.1 4.6 10.2": ["cochlea"], "5.8 1.9 -0.7": ["spokewoman"], "2.9 6.6 9.8": ["achilles"], "7.0 2.0 8.5": ["ith"], "10.7 -1.3 3.2": ["unsexy"], "2.2 6.3 3.0": ["traffics"], "6.1 16.5 15.0": ["microclimate"], "6.8 9.8 38.9": ["hollandaise"], "-2.1 16.0 5.9": ["baldly"], "16.0 9.2 28.7": ["coot"], "13.9 15.8 32.7": ["vole"], "0.3 17.1 10.1": ["caresses"], "-1.0 3.9 7.2": ["shuttler"], "-3.3 2.8 26.2": ["soymeal"], "1.9 26.6 1.1": ["counterattacked"], "9.5 14.0 4.0": ["snores"], "3.8 1.2 8.5": ["natatorium"], "-1.8 10.1 6.2": ["acetylcholine"], "-8.9 4.1 12.9": ["capris"], "9.5 -3.9 9.6": ["cloudier"], "0.4 21.4 3.1": ["bikies"], "10.3 1.9 12.1": ["asia"], "6.1 3.7 -2.8": ["indemnities"], "16.8 9.6 26.0": ["dipper"], "10.6 10.2 10.0": ["stymieing"], "5.9 13.6 4.9": ["truculent"], "6.0 15.7 7.2": ["purposed"], "13.8 7.2 13.2": ["willies"], "17.6 12.2 12.4": ["dollies"], "3.6 10.4 15.4": ["sheathing"], "-0.0 10.9 7.1": ["reestablishment"], "0.6 8.0 16.5": ["raster"], "0.1 5.2 11.8": ["https"], "6.2 8.4 6.2": ["pressbox"], "4.6 9.5 21.0": ["gar"], "6.1 6.1 4.9": ["unarguably"], "-9.8 14.0 6.7": ["communicable"], "-2.9 1.7 -1.3": ["neuropsychologist"], "-2.0 6.9 6.9": ["thymus"], "0.5 10.6 1.2": ["contextually"], "-5.3 7.8 6.0": ["interpolated"], "2.2 10.6 2.1": ["neutrally"], "3.4 3.5 4.9": ["landmarked"], "-12.2 1.3 6.0": ["geriatrician"], "2.2 7.8 3.3": ["entrusts"], "0.6 12.5 6.2": ["expediently"], "-0.0 3.3 6.0": ["measurables"], "3.1 14.1 32.0": ["saltiness"], "-10.1 4.0 -2.9": ["conscientiousness"], "1.8 1.2 8.8": ["wtih"], "12.1 10.5 4.6": ["lacerating"], "0.6 3.0 3.5": ["aboveboard"], "-3.1 -3.9 8.5": ["kerbside"], "-4.7 11.6 5.3": ["walkthroughs"], "0.3 11.8 5.1": ["forgers"], "14.2 24.5 3.2": ["nazi"], "-4.0 8.5 9.2": ["oratorical"], "-2.1 5.0 9.1": ["outrageousness"], "8.8 12.5 8.0": ["alcoves"], "1.7 4.5 7.7": ["mechanicals"], "2.9 9.5 5.4": ["herdsman"], "7.4 12.0 6.0": ["befuddle"], "1.6 9.1 1.1": ["nontaxable"], "6.5 13.9 6.0": ["stiffing"], "4.8 3.5 3.7": ["percents"], "1.4 -0.3 5.4": ["triglyceride"], "-2.4 16.0 8.0": ["psalm"], "14.5 7.3 8.9": ["dreamily"], "13.4 15.4 5.7": ["uninviting"], "1.4 30.1 14.4": ["cutscene"], "7.4 13.2 2.5": ["unanswerable"], "-13.2 9.8 0.5": ["psychopathology"], "2.5 5.1 7.6": ["naughtiness"], "-2.9 8.7 7.0": ["brunettes"], "3.2 13.8 6.5": ["brusquely"], "-1.0 5.3 -12.0": ["optioning"], "10.6 16.0 16.1": ["brambles"], "18.2 7.3 12.1": ["lumbers"], "13.2 10.3 18.8": ["spaniel"], "22.7 3.2 14.5": ["technicolor"], "-6.5 9.0 2.8": ["entreated"], "16.9 10.7 6.4": ["enema"], "-2.6 10.4 9.1": ["discontentment"], "5.8 15.8 1.8": ["meridian"], "-6.9 1.3 8.6": ["tonsillectomy"], "11.4 12.3 12.9": ["suffocates"], "8.5 10.2 35.9": ["finch"], "5.1 3.5 14.4": ["indigents"], "-0.3 18.9 7.8": ["cribbing"], "4.2 6.2 16.1": ["merrymaking"], "1.0 -1.2 9.1": ["nitrite"], "8.4 -6.4 4.3": ["yn"], "3.1 6.3 11.7": ["governmentwide"], "12.8 7.4 -1.8": ["photoshopped"], "-2.2 1.0 0.6": ["concordance"], "-4.5 9.5 7.1": ["demurrer"], "-0.4 9.8 -1.6": ["rejuvenates"], "13.4 10.4 11.3": ["youll"], "11.0 6.8 9.9": ["mimed"], "3.5 15.8 0.1": ["flypast"], "14.9 2.1 4.8": ["ambles"], "-3.8 9.3 5.4": ["chronograph"], "8.3 9.1 12.9": ["amphitheaters"], "-4.2 3.9 1.6": ["leniently"], "6.6 3.5 6.8": ["applets"], "10.9 24.4 14.0": ["copters"], "5.1 8.1 5.1": ["watchwords"], "3.3 10.4 13.2": ["retrovirus"], "-0.4 9.3 4.9": ["subunits"], "-1.3 8.0 -3.4": ["postion"], "1.4 11.1 4.9": ["approbation"], "-6.7 4.8 12.5": ["rezonings"], "1.9 16.0 2.2": ["excellency"], "2.3 18.3 6.2": ["bailiwick"], "8.0 6.9 13.6": ["coffer"], "2.0 10.1 5.6": ["frontbencher"], "7.2 -1.3 23.9": ["flaked"], "1.2 9.6 26.6": ["cheesesteaks"], "13.7 3.3 10.6": ["unscramble"], "4.8 1.0 6.6": ["watercooler"], "-4.6 3.8 -1.3": ["ner"], "-1.1 6.8 5.3": ["airballs"], "0.4 8.4 11.9": ["swale"], "7.8 -3.0 7.9": ["plasterer"], "2.0 10.1 11.1": ["buggery"], "-0.6 6.6 5.1": ["prob"], "6.0 7.3 4.0": ["prefixes"], "7.9 5.8 2.5": ["improvers"], "3.4 2.9 31.6": ["mascarpone"], "-4.2 5.3 14.0": ["dote"], "9.1 7.3 2.0": ["inscribe"], "4.9 19.3 3.6": ["sabotages"], "-11.9 13.7 7.9": ["fraternization"], "-3.5 9.3 12.5": ["tress"], "4.4 9.6 -1.5": ["interchanged"], "-9.3 11.1 2.7": ["platooning"], "-2.0 8.7 9.7": ["rebelliousness"], "0.7 19.5 6.0": ["rationalist"], "5.4 3.0 14.3": ["earlobe"], "1.1 6.0 8.6": ["reinsured"], "4.9 19.2 8.4": ["wingnuts"], "12.5 8.3 14.5": ["gatecrashers"], "16.5 6.6 4.5": ["somersaulting"], "-2.5 11.2 1.9": ["yardline"], "7.1 8.5 6.8": ["uestlove"], "-0.3 4.6 10.1": ["yogis"], "-1.4 0.3 10.1": ["podiatrists"], "11.8 4.5 13.9": ["crimps"], "3.3 20.3 1.4": ["againt"], "0.8 13.2 10.6": ["anorak"], "-5.1 4.5 4.2": ["mmbtu"], "9.4 6.3 11.7": ["microwaving"], "8.8 21.6 5.6": ["afterburners"], "2.7 30.7 10.2": ["wrongdoer"], "2.8 8.1 6.1": ["airmail"], "2.6 18.2 7.9": ["facemasks"], "5.3 -5.3 10.0": ["commencements"], "-1.9 -0.3 3.6": ["rhabdomyolysis"], "-0.8 4.8 42.3": ["paddlefish"], "5.3 2.6 10.5": ["tor"], "14.8 6.5 6.6": ["swindles"], "-5.0 6.1 5.3": ["underthrew"], "9.0 11.9 16.8": ["ummm"], "0.4 5.6 9.9": ["inelastic"], "-1.1 -2.7 16.0": ["grommets"], "-2.7 15.0 11.1": ["givens"], "2.3 6.2 6.5": ["measureable"], "11.7 6.2 4.1": ["commodification"], "-6.0 11.6 0.3": ["aptitudes"], "1.0 12.1 7.0": ["drunkards"], "-4.4 15.8 10.6": ["qubit"], "12.5 20.4 4.9": ["disfigure"], "-1.4 11.3 14.6": ["powerplays"], "21.0 5.7 4.1": ["jutted"], "-6.5 7.0 8.8": ["chafes"], "22.9 21.7 21.6": ["zeppelin"], "15.7 4.1 13.8": ["hubcap"], "-2.0 11.1 7.7": ["chits"], "-12.1 16.1 -1.0": ["smallbore"], "6.7 10.2 10.0": ["freehand"], "1.8 7.8 45.9": ["billfish"], "11.3 10.9 -2.4": ["sternest"], "-1.0 -0.8 -2.4": ["adenosine"], "7.1 8.3 7.3": ["shrewdest"], "4.5 21.0 3.1": ["parachutist"], "9.8 6.6 5.7": ["serendipitously"], "6.5 -0.5 2.6": ["corporatisation"], "-4.1 3.1 4.0": ["unstaffed"], "-5.4 12.0 3.3": ["destabilizes"], "-2.7 3.4 0.4": ["prosumer"], "-3.4 19.2 8.7": ["oddsmaker"], "3.2 19.8 3.7": ["fantasist"], "-12.0 5.1 11.2": ["overdubs"], "7.9 7.2 2.1": ["saturates"], "7.5 9.5 1.0": ["unmatchable"], "7.5 3.1 12.1": ["ginkgo"], "1.1 13.5 12.3": ["milo"], "1.9 8.7 8.0": ["pursed"], "-0.2 5.4 5.8": ["unfreezing"], "8.8 6.4 4.5": ["dominantly"], "4.2 15.6 5.2": ["incomparably"], "-2.4 15.6 -0.5": ["difficultly"], "5.9 8.2 9.3": ["quark"], "23.0 7.9 -1.8": ["megastore"], "14.2 -6.0 2.8": ["mths"], "0.1 17.9 11.5": ["venality"], "6.0 10.2 2.5": ["inversions"], "-1.4 3.2 8.4": ["circumcisions"], "0.8 8.2 8.8": ["namespace"], "3.3 7.3 0.4": ["knuckling"], "0.7 12.2 14.0": ["popout"], "13.0 -3.1 5.5": ["showpieces"], "-2.4 8.2 14.5": ["inebriation"], "5.5 -0.1 13.4": ["ironworkers"], "2.4 3.9 11.7": ["triplicate"], "24.4 6.6 5.2": ["chintzy"], "9.0 7.7 14.6": ["stepsisters"], "-2.3 3.3 4.0": ["agentless"], "11.8 12.7 4.3": ["floodlight"], "2.9 6.9 14.8": ["gastropub"], "10.5 11.9 11.4": ["chameleons"], "5.1 7.9 10.7": ["nonalcoholic"], "10.4 3.8 -4.5": ["stethoscopes"], "-1.6 1.9 5.2": ["miked"], "9.9 4.2 10.7": ["helix"], "-6.5 11.9 6.0": ["ciprofloxacin"], "19.5 33.5 18.0": ["orcs"], "-8.1 -1.6 -1.6": ["euphonium"], "5.3 9.4 8.6": ["bumble"], "-0.9 9.5 11.2": ["nonfactor"], "-9.2 4.8 8.6": ["foaled"], "-2.1 2.8 -3.8": ["administrate"], "-2.6 3.8 -3.4": ["promptness"], "5.2 2.5 14.6": ["feelin"], "4.9 0.2 11.3": ["stonemason"], "-0.6 5.5 18.1": ["bullocks"], "5.6 1.0 7.4": ["unscrewed"], "8.2 2.0 21.4": ["yaks"], "18.5 15.0 9.3": ["banksters"], "5.3 9.4 3.4": ["thirtieth"], "-6.3 2.9 3.6": ["pinfalls"], "10.1 1.8 7.5": ["whippet"], "4.4 4.5 11.9": ["usurious"], "9.6 -3.3 12.7": ["bioreactors"], "1.0 11.0 4.1": ["impost"], "7.7 17.0 16.0": ["hedgerow"], "9.1 8.4 -2.4": ["somersaulted"], "6.1 13.4 10.3": ["jarringly"], "2.3 2.1 9.4": ["showstoppers"], "5.3 7.0 14.5": ["cockney"], "-7.5 -1.8 10.3": ["bisphosphonate"], "9.7 14.1 9.0": ["animist"], "13.4 26.2 32.2": ["weevil"], "4.4 6.9 -1.8": ["scorns"], "-3.4 9.9 0.2": ["vitiate"], "3.0 5.8 7.1": ["bushings"], "9.0 9.7 10.6": ["aha"], "2.3 6.9 1.0": ["unpublicized"], "8.1 7.5 3.2": ["overselling"], "11.3 8.5 11.3": ["hatful"], "5.8 2.9 6.9": ["tonights"], "4.2 19.2 7.3": ["philanderer"], "-0.5 11.0 21.7": ["matzah"], "-4.6 10.5 13.5": ["biocides"], "-3.1 12.1 8.7": ["troposphere"], "-4.8 10.7 3.5": ["moisturize"], "7.1 8.8 6.9": ["thornier"], "14.1 2.6 13.7": ["stringed"], "2.5 18.6 12.1": ["ambiguously"], "37.4 7.5 7.8": ["monoliths"], "6.0 2.3 12.3": ["superjumbos"], "2.4 4.6 10.3": ["druggies"], "4.2 7.5 18.6": ["dachshunds"], "11.3 5.4 14.9": ["flowerpots"], "1.6 21.0 9.3": ["axioms"], "-1.0 1.6 6.3": ["beltline"], "-9.2 4.5 7.2": ["ponding"], "-0.0 -4.3 6.6": ["polyolefins"], "10.0 9.8 43.0": ["nutria"], "5.4 10.4 10.3": ["obverse"], "9.8 13.7 9.9": ["lustily"], "3.7 1.4 2.4": ["formers"], "-0.6 5.6 7.1": ["celecoxib"], "8.9 7.9 3.6": ["configurator"], "9.5 5.7 19.5": ["birdbath"], "3.4 18.0 8.9": ["bivouac"], "-8.4 6.4 3.6": ["dramatists"], "-5.4 4.4 11.1": ["mitosis"], "5.7 3.6 0.9": ["bronchial"], "6.6 6.5 28.6": ["sorrel"], "4.7 2.0 7.1": ["vim"], "2.6 6.2 35.1": ["filleted"], "8.4 3.2 30.4": ["curried"], "11.8 9.9 0.0": ["innovates"], "8.3 8.8 9.2": ["mousy"], "1.5 5.7 8.6": ["permissiveness"], "4.8 3.8 4.6": ["humidifiers"], "12.5 -0.4 17.2": ["fluted"], "1.7 6.9 7.7": ["coolants"], "-0.6 8.1 10.8": ["bavituximab"], "4.6 16.7 3.8": ["corporeal"], "19.0 4.2 12.1": ["freckled"], "0.5 -4.8 22.9": ["cheesemakers"], "-4.4 21.4 13.5": ["sensei"], "4.1 10.5 16.2": ["isthmus"], "-0.3 13.9 7.4": ["diffraction"], "-8.2 5.9 8.5": ["aspersions"], "-1.1 13.7 9.1": ["procrastinator"], "-1.0 21.7 5.3": ["invidious"], "4.3 20.7 -0.5": ["humiliates"], "-7.9 14.5 8.0": ["enunciation"], "-4.9 14.9 8.0": ["termer"], "-0.3 7.9 3.8": ["ethno"], "-3.5 8.4 5.5": ["picturized"], "25.0 9.8 7.0": ["sandpit"], "5.2 15.3 13.8": ["gangbangers"], "-4.1 4.2 10.5": ["decongestant"], "11.6 3.7 3.3": ["fromthe"], "-3.2 2.5 4.9": ["bilirubin"], "2.7 27.9 0.8": ["fascistic"], "8.9 -1.9 1.6": ["bookrunner"], "3.5 -1.6 19.0": ["moratoria"], "1.5 -3.5 9.2": ["coker"], "5.3 8.7 -7.0": ["convulsive"], "4.8 8.2 4.3": ["murmurings"], "-3.4 6.8 10.9": ["dobro", "committes"], "3.6 -2.7 9.0": ["chaperoning"], "6.3 2.2 13.2": ["nylons"], "-3.8 2.8 1.3": ["sedating"], "-1.4 14.3 11.0": ["charterer"], "-1.9 7.3 12.7": ["skippering"], "1.0 15.6 10.6": ["impoverishing"], "8.5 9.0 9.8": ["twits", "adsl"], "-6.8 4.1 5.1": ["radioisotopes"], "-2.9 8.9 9.4": ["whitelist"], "7.1 3.1 12.0": ["accordions"], "9.4 8.9 17.5": ["deltas"], "5.3 11.7 4.9": ["smilingly"], "6.4 13.6 7.4": ["helipads"], "16.8 1.4 -2.2": ["writeoff"], "11.5 8.8 7.2": ["superfan"], "5.9 5.1 21.0": ["miter"], "14.5 8.2 4.0": ["hypes"], "-0.7 8.6 12.3": ["khan"], "-7.0 -1.1 14.6": ["neckwear"], "-5.2 12.0 12.6": ["overacting"], "0.4 13.9 7.4": ["microsecond"], "-5.2 3.9 -1.6": ["flydubai"], "2.6 7.1 6.0": ["chambered"], "14.4 3.0 5.6": ["kitting"], "10.3 16.1 10.1": ["ritually"], "10.8 4.2 5.5": ["scalpels"], "4.9 -5.8 2.4": ["workability"], "-5.8 16.5 3.2": ["enunciate"], "-0.7 14.2 7.2": ["invalids"], "7.9 9.7 4.6": ["patentee"], "3.9 4.4 9.2": ["everolimus"], "4.7 19.5 1.2": ["covey"], "-3.2 8.5 4.2": ["handovers"], "10.1 7.9 7.0": ["presages"], "1.5 7.7 11.3": ["butters"], "4.4 12.8 5.6": ["expansively"], "-8.3 8.1 -0.3": ["encumber"], "16.7 4.8 13.5": ["gerbils"], "12.4 7.3 27.6": ["wieners"], "-3.2 6.5 5.6": ["vocalizing"], "-0.8 13.3 13.8": ["overanxious"], "-5.2 7.3 12.7": ["coliform"], "4.3 5.1 13.0": ["legendarily"], "13.6 1.9 10.5": ["adios", "drywalls"], "-3.4 2.7 -4.3": ["talktime"], "10.9 12.8 9.1": ["chatters"], "3.6 12.4 4.2": ["fortifies"], "-15.4 3.7 10.6": ["numismatic"], "-2.2 5.8 17.7": ["lahar"], "-3.0 -3.3 -4.0": ["compliancy"], "-2.7 14.9 3.3": ["repressions"], "2.0 9.4 11.1": ["schoolmaster"], "-3.3 10.9 0.3": ["interregnum"], "17.5 5.1 14.1": ["cherubs"], "0.6 3.8 0.7": ["radiofrequency"], "15.5 9.5 20.9": ["terrarium"], "14.8 10.2 20.2": ["freeloading"], "13.2 4.0 2.6": ["ultrafast"], "-2.1 0.4 2.5": ["reformatory"], "16.1 12.8 15.2": ["cornstalks"], "8.8 0.2 7.2": ["hungering"], "-5.6 3.1 2.6": ["hyponatremia"], "0.2 21.3 6.0": ["foreknowledge"], "13.9 -3.8 7.7": ["glutted"], "9.8 -0.1 11.3": ["flume"], "-0.5 2.4 -3.2": ["telephonically"], "5.2 -0.5 -0.9": ["conf"], "2.9 13.6 5.9": ["realness"], "-2.5 -5.2 2.8": ["masterclasses"], "5.7 8.3 8.3": ["gmail"], "-4.1 5.6 5.5": ["xylitol"], "4.8 7.1 8.8": ["meetup"], "2.6 12.1 16.7": ["amulet"], "2.6 19.8 17.7": ["submariner"], "8.4 12.1 9.2": ["shits"], "-8.7 10.1 3.5": ["libertine"], "5.7 -6.1 -0.9": ["digitalization"], "2.9 10.3 13.2": ["gentility"], "2.6 12.5 9.3": ["nitrous"], "3.7 8.8 4.7": ["horrify"], "7.5 7.6 4.5": ["repossessing"], "17.3 3.7 11.6": ["grandees"], "-9.2 12.2 11.7": ["bortezomib"], "11.4 2.3 20.3": ["oceanographers"], "14.4 15.4 3.5": ["threateningly"], "18.9 10.1 9.1": ["engorged"], "10.8 3.2 13.0": ["shoemakers"], "18.4 3.3 11.2": ["trussed"], "0.9 12.6 4.0": ["unfenced"], "1.2 19.6 5.8": ["armoring"], "-4.8 10.0 6.9": ["daylighting"], "10.8 6.2 21.3": ["curds"], "-3.2 3.5 6.4": ["ideation"], "6.3 9.0 15.1": ["bada"], "12.8 30.3 16.7": ["brigands"], "-1.3 3.6 6.8": ["hantavirus"], "-4.0 7.9 9.2": ["melodically"], "5.3 6.8 16.7": ["nuttiness"], "-1.9 2.0 10.7": ["clawbacks"], "-1.9 2.5 4.7": ["radiothon"], "-2.7 13.0 18.1": ["mma"], "12.6 20.9 -4.2": ["unsuspected"], "11.0 14.1 1.2": ["visualizes"], "11.2 10.8 8.8": ["laziest"], "-7.2 5.4 6.9": ["outtake"], "-2.4 11.6 11.8": ["topweight"], "2.8 8.9 -3.7": ["disrobed"], "7.7 8.5 14.9": ["luminaria"], "4.4 11.8 2.2": ["gratify"], "0.8 7.7 10.6": ["pretentiousness"], "18.3 2.4 18.2": ["tallow"], "2.3 10.2 27.8": ["chicory"], "2.7 3.9 5.1": ["decorous"], "10.7 10.9 6.6": ["alarmism"], "7.5 9.9 -0.8": ["pornographer"], "-0.5 8.4 9.0": ["earbud"], "-0.2 3.4 10.9": ["herbalists"], "14.2 10.4 1.6": ["handstands"], "-6.2 8.9 -5.3": ["dissociate"], "17.6 15.2 3.1": ["truckmaker"], "12.6 8.9 6.5": ["amazon"], "2.0 5.5 13.5": ["jammy"], "-7.9 6.8 0.1": ["pulmonologist"], "7.0 5.5 12.4": ["parkade"], "6.8 -2.6 10.6": ["wholesales"], "1.9 4.8 2.9": ["vivacity"], "11.6 5.7 10.6": ["bon"], "3.4 16.5 18.2": ["cunt"], "6.6 4.3 6.9": ["soundstages"], "2.6 6.9 5.8": ["taxonomies"], "11.0 2.1 9.3": ["largescale"], "9.5 14.7 8.3": ["scampers"], "2.3 13.3 12.6": ["traditionalism"], "9.9 10.3 23.6": ["darter"], "-8.7 -2.3 21.8": ["oocytes"], "15.9 -6.3 6.3": ["gatecrashed"], "22.6 7.1 16.7": ["keeled"], "4.2 8.4 14.5": ["insourcing"], "13.1 11.0 6.1": ["boggle"], "2.0 4.5 9.1": ["tippers"], "7.6 13.6 5.5": ["cartographer"], "2.3 13.0 9.4": ["snogging"], "0.3 8.7 11.7": ["pinion"], "4.2 12.4 4.8": ["leaper"], "3.7 12.0 1.7": ["personae"], "1.8 14.3 25.7": ["earthenware"], "11.2 1.3 5.4": ["confessionals"], "15.0 7.2 16.6": ["foretells"], "8.2 3.3 24.1": ["defrosted"], "-4.1 15.1 -0.6": ["addressee"], "-2.8 4.3 42.7": ["waterman"], "6.7 2.6 5.6": ["clubrooms"], "28.2 8.9 15.8": ["squiggly"], "1.3 13.6 11.1": ["undrinkable"], "7.5 8.5 11.2": ["slogs"], "-0.3 7.4 10.0": ["wicketless", "cytomegalovirus"], "-4.3 0.6 -4.1": ["ultracapacitors"], "1.1 8.9 8.0": ["earthwork"], "6.4 1.2 13.4": ["handcrafts"], "-3.5 11.2 4.4": ["gradations"], "13.2 16.3 10.5": ["screamers"], "3.1 -1.2 1.8": ["cds"], "-3.3 10.5 13.4": ["estimators"], "0.2 4.6 2.1": ["pressmen"], "1.6 3.1 8.8": ["soundcheck"], "2.5 12.1 4.9": ["schemas"], "5.1 2.6 9.1": ["behaviorally"], "8.7 -3.9 8.3": ["lathered"], "17.4 -0.3 16.1": ["beaker"], "-1.8 2.6 10.8": ["pujas"], "10.0 21.5 24.0": ["mongoose"], "-0.1 4.6 4.3": ["tanneries"], "-4.5 4.9 2.6": ["lacunae"], "9.5 -1.3 7.8": ["whistler"], "10.6 9.1 3.9": ["runnin"], "3.3 -6.7 12.9": ["seasonable"], "15.5 2.5 7.4": ["enviously"], "13.4 14.1 1.0": ["equidistant"], "13.6 10.5 17.6": ["coiling"], "7.6 16.0 13.9": ["gatherer"], "10.7 9.9 12.7": ["antelopes"], "8.9 14.7 5.8": ["nearness"], "-4.8 8.2 1.3": ["soloed"], "5.9 1.4 0.7": ["basketballer"], "7.4 21.2 5.7": ["detonates"], "8.5 9.8 0.6": ["clarion"], "4.9 13.7 1.7": ["altimeter"], "1.6 0.1 -2.5": ["disburses"], "2.9 5.0 4.5": ["cytoskeleton"], "-2.7 13.4 8.3": ["dehydrating"], "-0.8 10.2 4.1": ["concord"], "3.1 8.6 -0.8": ["embolism"], "4.6 3.9 14.2": ["stepper"], "7.9 7.3 4.9": ["impotency"], "7.2 3.4 2.7": ["riskiness"], "2.1 3.5 17.3": ["axon"], "-0.0 5.8 4.6": ["subpoenaing"], "5.2 20.1 10.1": ["coven"], "-2.5 10.9 3.8": ["deconstructs"], "-2.5 2.7 9.6": ["parker"], "-2.6 7.0 -1.3": ["wicks"], "-11.0 8.3 0.4": ["ulama"], "-6.0 3.2 8.3": ["cellists"], "-0.1 8.9 11.8": ["kanals"], "3.2 2.2 4.9": ["enthronement"], "5.1 17.4 7.2": ["peripheries"], "14.7 9.4 11.5": ["adj"], "6.6 15.9 25.6": ["seasickness"], "7.5 -5.3 5.8": ["rm"], "6.4 2.7 17.6": ["stave"], "3.1 9.5 8.2": ["puritan"], "12.7 8.2 10.5": ["toymakers"], "6.3 4.5 2.1": ["ailed"], "-1.4 10.6 13.2": ["precipitates"], "-2.0 7.2 6.0": ["familes"], "-4.7 12.6 8.9": ["satisfactions"], "-11.1 13.0 15.5": ["batterers"], "6.7 20.7 13.7": ["frostbitten"], "-2.4 16.6 4.6": ["dispossess"], "-4.6 5.6 3.5": ["overexpressed"], "-1.4 1.1 -3.7": ["redrafting"], "12.8 13.6 -2.7": ["rudest"], "-6.7 6.8 1.7": ["thallium"], "8.1 15.0 24.8": ["whoppers"], "2.7 6.6 8.2": ["autocad"], "-0.7 19.9 6.3": ["encumbrance"], "12.1 -2.1 -2.1": ["masqueraded"], "16.8 -4.0 3.7": ["moots"], "-7.0 15.1 12.2": ["redistrict"], "4.7 3.6 -4.0": ["retrievable"], "-1.2 11.1 8.6": ["uncrowded"], "8.8 16.1 -1.4": ["embodiments"], "-12.3 4.1 -0.1": ["neuroimaging"], "11.4 7.0 3.3": ["bedspreads"], "-2.4 10.8 46.3": ["bonefish"], "7.8 10.0 2.5": ["recognizably"], "-6.2 7.8 12.2": ["grouses"], "12.3 19.0 7.2": ["infernos"], "11.7 -4.9 8.1": ["slimmed"], "-3.8 12.2 3.5": ["indigene"], "1.9 1.5 34.0": ["sauced"], "0.8 12.3 0.0": ["libeled"], "3.0 0.2 13.5": ["lan"], "4.0 9.3 7.2": ["precariousness"], "6.5 -5.6 2.5": ["sorters"], "4.5 15.3 5.1": ["seatmate"], "11.8 14.8 5.9": ["gentlest"], "15.0 8.5 3.3": ["swingeing"], "-2.3 3.2 10.7": ["skicross"], "15.4 7.3 6.8": ["sculpts"], "5.2 5.7 15.1": ["fallaway"], "3.3 10.3 2.6": ["toughing"], "-2.1 5.6 3.7": ["medicating"], "1.0 8.8 9.6": ["housebroken"], "12.6 3.7 9.5": ["flatline"], "15.3 2.4 8.3": ["tambourines"], "14.1 9.0 14.7": ["twitched"], "18.6 24.5 11.9": ["weaklings"], "-2.8 6.3 -4.9": ["wouldn"], "-9.5 31.2 7.7": ["downrange"], "-2.0 20.3 6.7": ["overflight"], "-0.7 24.5 9.6": ["gentiles"], "11.9 9.1 0.9": ["undimmed"], "11.1 8.9 14.7": ["cockeyed"], "-0.2 6.7 2.1": ["topically"], "6.2 11.2 12.5": ["stickhandling"], "0.8 13.1 2.3": ["proscription"], "2.5 7.2 29.5": ["omelettes"], "6.1 13.2 5.3": ["cyclonic"], "7.1 12.5 22.0": ["switchblade"], "12.5 5.7 10.3": ["scrubby"], "3.9 5.0 3.8": ["intervenors"], "1.0 8.0 2.4": ["impersonates"], "3.3 18.5 7.7": ["potentiality"], "-3.9 10.8 11.6": ["bhai"], "6.3 6.5 1.2": ["contouring"], "10.2 7.7 9.8": ["skanky"], "5.4 0.7 35.2": ["terrine"], "-3.8 -3.1 6.6": ["finagle"], "4.3 1.6 2.9": ["tuneups"], "-2.8 7.4 5.0": ["immobilizer"], "11.7 26.0 4.7": ["thermonuclear"], "8.3 6.8 -0.1": ["crematoria"], "-4.9 7.0 7.9": ["hedgers"], "1.7 2.2 1.8": ["astrobiology"], "-4.2 8.1 12.0": ["frizz"], "-2.1 2.6 5.8": ["endoscopes"], "12.8 3.0 12.6": ["slosh"], "3.9 5.2 8.0": ["lookups"], "5.2 2.6 13.8": ["preheated"], "7.2 9.9 0.5": ["expends"], "-0.5 -2.1 9.5": ["bookkeepers"], "25.0 7.1 4.6": ["erects"], "18.6 2.1 13.1": ["matchstick"], "-5.3 7.2 3.1": ["obligor"], "12.6 14.2 7.6": ["benignly"], "3.6 6.6 0.5": ["flexion"], "17.2 6.2 15.8": ["disgorged"], "-2.0 7.6 15.2": ["inboard"], "12.5 4.7 15.3": ["ese"], "2.1 10.7 17.0": ["muff"], "12.7 9.5 12.2": ["chortled"], "-1.9 6.9 3.6": ["uniques"], "0.8 7.4 33.4": ["chickpea"], "-3.0 8.6 -5.3": ["elucidating"], "4.4 17.2 4.8": ["recalibrating"], "11.7 11.0 8.1": ["hewing"], "8.8 13.5 4.7": ["hyphens"], "-0.8 10.0 26.0": ["azalea"], "11.3 8.5 9.8": ["matadors"], "3.6 7.9 0.7": ["droned"], "-0.2 16.9 30.6": ["spinnerbait"], "9.0 7.1 1.2": ["dribs"], "1.7 0.9 8.0": ["pipework"], "-3.1 12.4 4.5": ["infeasible"], "-1.8 3.7 11.3": ["ghats"], "2.0 10.3 16.1": ["mulligans"], "-0.8 14.2 13.2": ["dislocate"], "-1.1 1.8 14.1": ["bolero"], "17.5 9.9 12.6": ["igloos"], "10.9 20.0 9.9": ["illogic"], "14.4 0.8 18.3": ["gilding"], "8.4 5.7 23.0": ["ibis"], "1.7 6.5 7.9": ["cribbed"], "-3.6 3.0 8.9": ["holdback"], "8.7 7.5 2.9": ["pocketable"], "13.9 16.5 6.3": ["beneficent"], "13.0 2.5 13.2": ["parquet"], "-1.4 12.1 9.4": ["remounted"], "5.8 4.3 9.9": ["whist"], "0.0 7.7 12.7": ["networker"], "3.6 1.7 3.2": ["tenge"], "5.8 30.3 15.9": ["waypoint"], "7.2 13.2 11.3": ["gnaws"], "6.5 7.1 4.6": ["storerooms"], "-8.3 1.2 6.4": ["mentees"], "-1.7 0.6 3.7": ["postgraduates"], "-4.3 6.6 20.1": ["chutneys"], "3.1 8.4 23.0": ["opossums"], "0.6 6.7 4.0": ["gapping"], "6.7 9.2 9.3": ["luv"], "-4.5 8.8 9.1": ["gallopers"], "2.9 12.3 1.2": ["ascendency"], "1.2 10.2 -4.0": ["causative"], "7.4 12.9 5.8": ["unaccountably"], "-3.5 -4.6 7.0": ["saleyards"], "10.3 12.5 21.2": ["jowls"], "14.3 3.8 42.5": ["seahorses"], "0.3 20.0 2.8": ["reoccupy"], "-5.1 9.8 9.1": ["alternation"], "8.0 18.7 16.6": ["rooks"], "4.7 13.6 20.2": ["runback"], "7.2 21.5 5.0": ["trespasses"], "18.1 -2.6 10.5": ["ponytailed"], "2.1 1.2 2.9": ["biocompatible"], "-1.8 3.2 19.4": ["bronzer"], "-4.7 10.2 19.9": ["bighorns"], "6.9 11.5 16.2": ["littler"], "-6.1 8.4 8.6": ["germplasm"], "-8.9 6.2 5.0": ["shapewear"], "5.6 1.7 5.1": ["eventuated"], "8.2 0.1 6.5": ["tragicomic"], "9.0 5.4 10.7": ["synthetically"], "-1.7 -1.2 4.5": ["ovulating"], "3.2 8.9 6.3": ["deuterium"], "0.2 5.6 18.1": ["flanges"], "1.5 14.2 4.3": ["refracted"], "4.3 -3.9 5.6": ["roper"], "4.6 6.9 11.3": ["goalbound"], "8.2 8.7 0.8": ["slaving"], "8.8 2.3 10.8": ["uncorking"], "7.0 10.2 12.4": ["petaflop", "microgames"], "3.5 5.9 15.3": ["multiagency"], "1.5 0.0 7.1": ["datacom"], "23.7 18.9 19.7": ["buccaneers"], "10.9 16.0 18.8": ["thistles"], "1.7 4.9 6.2": ["autopsied"], "13.9 18.8 4.4": ["dunce"], "4.0 6.1 6.3": ["beatnik"], "5.7 16.2 6.8": ["indifferently"], "6.7 2.2 9.1": ["myrrh"], "4.5 6.8 4.4": ["broadbased"], "4.1 1.7 12.9": ["poppin"], "5.9 20.8 4.8": ["rearmament"], "10.5 8.5 21.1": ["schnitzel"], "6.9 9.3 13.6": ["woulda"], "11.4 7.0 8.5": ["industrialize"], "1.9 7.4 5.2": ["confiscations"], "2.0 10.9 11.8": ["centreback"], "12.1 8.1 12.0": ["heh"], "3.2 12.2 4.2": ["outduel"], "8.6 -1.4 13.6": ["boas"], "6.3 -9.0 13.4": ["ei"], "-1.3 22.7 7.7": ["islam"], "9.0 4.6 8.6": ["resonator"], "-2.2 0.8 7.6": ["carotid"], "12.2 3.4 14.7": ["pcs"], "18.0 -0.7 8.1": ["flotations"], "1.0 -3.6 17.0": ["winglets"], "7.9 14.4 11.6": ["accenting"], "1.8 6.6 2.0": ["abt"], "6.3 11.0 3.5": ["whoring"], "1.8 32.2 9.4": ["unbelief"], "1.9 5.7 -2.3": ["inducts"], "8.9 7.0 13.5": ["stomachache"], "2.5 14.9 4.9": ["perversions", "maltreating"], "-6.3 6.9 4.5": ["lorazepam"], "-3.0 7.6 10.0": ["volatilities"], "2.4 3.9 11.4": ["sik"], "-2.2 28.4 3.1": ["antiterrorist"], "-2.0 -7.7 5.3": ["microloans"], "11.3 8.9 4.6": ["orgs"], "5.9 3.9 21.1": ["macaroons"], "-1.0 4.5 11.7": ["lensing"], "-3.4 10.3 1.8": ["sanitizers"], "0.6 5.4 13.7": ["chocolatiers"], "4.1 9.6 6.4": ["indentured"], "-0.3 6.3 31.2": ["antipasto"], "13.8 4.6 9.5": ["ls"], "14.1 11.3 2.0": ["outperformer"], "4.9 4.2 7.0": ["yeh"], "12.5 5.6 8.1": ["lording"], "10.3 10.9 3.2": ["shinning"], "7.6 5.9 13.2": ["joiners"], "4.0 5.7 6.7": ["zirconium"], "13.6 11.4 3.2": ["blowhards"], "9.2 14.6 10.1": ["killjoy"], "4.3 16.6 15.4": ["photosynthetic"], "-4.9 4.9 6.4": ["bupropion"], "-4.0 7.3 5.4": ["ragas"], "-2.2 -1.3 -2.0": ["arbitrated"], "9.3 5.8 17.7": ["mastiff"], "-11.6 5.6 5.6": ["ghazals"], "-0.8 5.7 2.1": ["oversell"], "-7.3 7.6 43.4": ["clamming"], "-0.0 2.7 2.3": ["writeup"], "19.8 12.1 19.8": ["treacle"], "1.3 1.1 6.7": ["wonkish"], "6.8 -8.4 21.4": ["mee"], "12.0 4.3 4.8": ["ravers"], "-6.1 -2.1 16.0": ["perf"], "-0.1 3.7 2.3": ["ity"], "9.3 6.9 4.6": ["bifocals"], "-6.3 6.7 3.8": ["impaneled"], "-1.5 1.7 7.5": ["premia"], "-1.5 0.7 8.3": ["hemophiliacs"], "4.8 5.0 5.9": ["coalface"], "11.7 16.8 4.2": ["absorber"], "-0.3 7.1 8.7": ["nonconformist"], "2.5 19.0 4.9": ["prophetically"], "4.2 11.4 25.2": ["mimosa"], "2.8 4.3 11.0": ["soundboard"], "8.0 8.3 8.9": ["seance"], "-0.3 8.9 2.1": ["conceives"], "-3.0 4.0 1.9": ["unplowed"], "15.0 6.3 15.1": ["bongo"], "8.2 3.5 2.4": ["mosey"], "11.8 13.4 18.5": ["mournfully"], "8.9 15.7 17.4": ["powerbomb"], "12.2 16.0 8.9": ["klutz"], "-7.3 8.4 5.7": ["extrinsic"], "3.6 2.4 2.2": ["merchandised"], "4.8 8.5 1.9": ["emigre"], "11.5 2.5 23.3": ["flavorless"], "11.2 5.6 6.4": ["movin"], "8.8 7.8 32.0": ["schooners"], "2.6 2.0 13.3": ["varnished"], "13.1 9.7 14.7": ["shriveling"], "4.0 8.6 11.7": ["verandas"], "4.7 11.1 29.6": ["ratatouille"], "-4.6 7.5 14.0": ["singletrack"], "13.7 10.6 3.8": ["unromantic"], "7.5 13.7 12.0": ["menfolk"], "8.1 3.7 14.6": ["promenades"], "13.6 9.1 7.7": ["obsessives"], "0.7 9.1 8.3": ["submersion", "fractionalized"], "-5.2 2.8 6.3": ["intraoperative"], "14.6 8.1 4.5": ["chortling"], "13.5 11.2 44.9": ["mollusk"], "-1.8 -4.1 8.0": ["bicycled"], "7.6 11.2 22.2": ["hereabouts"], "7.7 5.8 12.1": ["unpermitted"], "10.1 -7.5 4.8": ["piggybacked"], "5.3 23.2 7.8": ["simplistically"], "-6.4 7.2 4.2": ["consistant"], "3.0 14.5 9.0": ["roughhousing"], "16.6 29.0 10.5": ["earthlings"], "13.7 10.9 11.1": ["brainiac"], "5.1 10.4 29.0": ["topwaters"], "-6.0 0.4 6.0": ["overburdening"], "6.0 3.5 7.8": ["midi"], "-1.1 11.3 11.8": ["snakebite"], "4.6 10.7 3.3": ["bulling"], "-8.8 19.4 7.9": ["corporals"], "-0.8 9.0 0.4": ["enjoins"], "-6.1 7.8 4.7": ["discursive"], "-4.2 2.1 7.7": ["histological"], "-5.4 6.5 4.5": ["cutaneous"], "2.1 22.6 -0.7": ["overstretch"], "6.3 10.4 31.2": ["larder"], "2.5 -5.5 5.5": ["geoscientists"], "0.6 -3.6 18.0": ["jen"], "1.7 -2.2 12.4": ["udder"], "-5.0 14.8 8.0": ["mediamen"], "5.4 7.1 10.1": ["ramblers"], "18.3 22.0 21.7": ["trident"], "11.5 7.7 -2.6": ["swigging"], "-7.9 9.2 4.5": ["overachieve"], "8.6 3.3 18.0": ["tawny"], "1.1 5.8 7.8": ["yarmulke"], "2.9 0.7 6.6": ["ci"], "1.9 5.2 8.0": ["soppy"], "5.8 5.7 5.9": ["overtone"], "4.0 3.2 2.2": ["skirmished"], "5.5 7.0 9.5": ["highlighter"], "-2.2 8.6 8.7": ["adoptee"], "-1.6 0.2 13.2": ["kasi"], "-2.4 -3.9 6.2": ["glycerol"], "34.6 5.8 13.3": ["humungous"], "-6.8 13.0 7.5": ["summited"], "6.9 15.1 15.1": ["unmoored"], "7.5 12.2 12.4": ["euphemistic"], "10.2 3.9 3.0": ["unnoticeable"], "1.7 2.4 4.2": ["sanatorium"], "3.8 15.2 5.3": ["obfuscated"], "3.9 17.3 8.0": ["inexcusably"], "5.9 9.8 13.0": ["sander"], "-0.1 11.7 3.6": ["discomfiting"], "6.5 -4.4 3.1": ["ser"], "0.4 2.5 1.8": ["disaggregated"], "-3.8 16.4 3.5": ["hideaways"], "16.9 5.9 6.2": ["unscrew"], "20.0 12.0 30.9": ["popper"], "13.2 18.0 12.9": ["scrim"], "8.9 6.2 12.1": ["modeler"], "15.8 10.9 33.8": ["albatrosses"], "13.6 27.6 7.5": ["pentagon"], "-12.0 14.2 4.5": ["pickoffs"], "5.3 -1.4 13.0": ["mudflow"], "5.3 6.9 4.6": ["exorbitantly"], "-11.2 5.8 20.4": ["haying"], "1.1 0.6 12.5": ["rapamycin"], "-3.9 8.4 8.4": ["unvested"], "-4.2 3.8 12.9": ["stabling"], "3.8 8.7 11.0": ["unhampered"], "-6.4 15.6 4.8": ["uncorrelated"], "11.0 19.0 5.4": ["wormhole"], "16.4 14.7 7.8": ["vortices"], "-1.2 15.2 -2.4": ["desensitize"], "9.0 3.8 9.0": ["salubrious"], "-3.2 17.7 6.1": ["untouchability"], "8.0 3.3 8.2": ["unibody"], "4.6 6.5 25.6": ["eaglets"], "-8.1 5.4 16.4": ["interscholastic"], "12.1 11.8 11.2": ["jobber"], "-2.9 4.8 3.3": ["extortions"], "-6.9 4.9 1.7": ["formulators"], "-4.6 5.8 1.6": ["fieldbus"], "10.4 -0.3 16.9": ["banquettes"], "-7.8 1.8 8.8": ["oxycontin"], "4.3 0.8 3.3": ["quietened"], "-2.5 0.5 -3.8": ["liason"], "-3.8 11.2 2.0": ["overtopped"], "-3.1 23.2 1.6": ["humanizes"], "5.7 8.6 7.3": ["sniggering"], "-0.9 7.5 5.3": ["irking"], "-3.5 5.3 4.5": ["enumerates"], "3.8 13.2 10.8": ["snog"], "2.6 6.6 4.9": ["toggles"], "3.8 13.7 6.5": ["flippantly"], "-10.6 8.6 1.6": ["elucidation"], "9.9 11.6 2.6": ["rbl"], "2.4 14.0 16.7": ["otaku"], "5.4 19.1 2.5": ["redeemer"], "3.0 8.6 3.5": ["herewith"], "-9.6 9.5 5.2": ["improvisers"], "-4.6 9.9 20.1": ["snowmachine"], "7.7 6.8 1.8": ["schoolroom"], "-0.4 7.7 12.1": ["pigmented"], "5.6 13.4 -0.5": ["dynamited"], "6.2 15.4 1.1": ["insignias"], "3.9 4.3 2.6": ["misclassification", "squeeked"], "8.4 7.4 15.2": ["krone"], "-7.8 3.9 8.6": ["hygienist"], "-4.4 12.4 3.4": ["backbenches"], "-3.0 5.2 11.9": ["rebuy"], "17.3 6.5 6.1": ["belched"], "-3.8 -0.3 6.1": ["topscored"], "0.7 -8.0 -0.2": ["prequalification"], "1.4 18.4 5.8": ["potentialities"], "-4.3 0.7 13.2": ["framer"], "-1.5 4.9 23.7": ["hundredweight"], "-5.2 11.1 -2.1": ["attenuate"], "0.8 4.5 6.1": ["thr"], "-12.3 1.3 17.0": ["rabi"], "0.3 10.5 -2.0": ["commiting"], "3.3 2.0 8.4": ["reb"], "-4.5 13.4 9.8": ["backcourts"], "2.9 12.3 13.4": ["sukkah"], "-8.7 9.9 11.1": ["periodontitis"], "-1.1 12.8 0.7": ["haredim"], "6.6 11.4 8.3": ["tantalize"], "13.3 22.0 11.6": ["naysayer"], "-0.3 10.6 9.2": ["clammed"], "6.9 -1.4 14.2": ["colorings"], "5.0 4.0 8.9": ["len"], "4.6 7.0 2.0": ["varenicline"], "5.7 5.2 13.8": ["luminescence"], "-7.3 8.8 1.8": ["netback"], "-12.5 4.7 0.3": ["hematocrit"], "-7.4 10.9 0.4": ["intubation"], "7.6 8.8 7.1": ["nametag"], "12.3 7.7 5.9": ["saunters"], "-2.7 8.6 4.2": ["oncogene"], "4.3 6.8 9.2": ["freemium"], "1.9 -3.3 7.2": ["orginally"], "-9.3 14.5 2.8": ["oversteps"], "-5.9 13.3 4.1": ["traumatize"], "6.6 9.4 -1.0": ["atria"], "15.2 0.2 10.8": ["swiss"], "2.2 4.4 15.1": ["skint"], "-3.0 10.4 12.5": ["speciation"], "9.2 5.8 5.1": ["keyboarding"], "2.2 4.8 12.7": ["hallucinogen"], "1.5 10.7 10.8": ["bloods"], "4.9 3.0 18.5": ["piggery"], "-0.2 3.2 4.6": ["quadricep"], "2.4 4.8 0.7": ["fireproofing"], "-4.3 4.6 4.1": ["intertwines"], "4.2 6.5 -0.0": ["gossiped"], "2.9 16.9 2.9": ["pallbearer"], "7.6 9.0 -2.5": ["cynosure"], "-1.0 12.9 -3.4": ["vituperative"], "8.6 5.0 3.0": ["disbands"], "-4.4 10.2 -2.2": ["salience"], "0.9 20.1 2.2": ["enrages"], "-0.7 10.8 14.3": ["backlinks"], "-4.7 6.1 10.3": ["procedurals"], "9.8 0.2 9.5": ["segmental"], "7.9 9.7 6.2": ["snowdrift"], "0.5 9.4 8.0": ["dotes"], "1.9 21.3 2.6": ["seducer"], "-1.3 16.9 1.3": ["moralist"], "8.6 11.8 14.1": ["birdbaths"], "6.1 14.3 0.4": ["undisputable"], "4.4 0.8 -2.0": ["ousters"], "7.6 5.9 13.1": ["muti"], "7.8 -0.5 11.9": ["php"], "-0.6 9.3 -0.1": ["chroniclers"], "3.4 9.5 11.9": ["complexions"], "23.0 13.1 11.1": ["bodacious"], "-13.3 5.8 4.4": ["revocations"], "16.9 27.6 19.7": ["viper"], "0.6 12.9 24.5": ["rhizomes"], "2.0 4.9 6.2": ["hydrophilic"], "5.2 19.3 0.4": ["outgun"], "-3.2 10.2 1.0": ["persuasiveness"], "-1.8 6.6 6.8": ["consuls"], "4.4 9.9 0.8": ["aerie"], "2.3 8.1 5.7": ["prefered"], "10.6 9.5 9.4": ["homogenization"], "10.1 5.0 3.0": ["smartbooks"], "8.1 13.3 25.8": ["fang"], "0.1 2.8 13.6": ["thi"], "8.1 4.2 13.9": ["bunions"], "5.2 9.1 8.4": ["crackhead"], "3.7 8.0 16.3": ["conviviality"], "-2.5 6.7 -0.8": ["withdrawl"], "4.2 5.7 1.6": ["taglines"], "-2.5 1.6 5.5": ["reeve"], "9.5 20.1 4.6": ["blackmailer"], "10.2 25.8 13.4": ["warlock"], "-0.5 8.0 4.3": ["roughs"], "10.1 11.4 8.3": ["inhales"], "-1.7 -2.0 15.5": ["tweeds"], "-4.2 -2.6 0.2": ["tgt"], "-10.2 22.5 5.9": ["fraternizing"], "0.2 8.4 0.4": ["bogie"], "-10.7 5.6 1.1": ["implementable"], "17.5 9.5 9.1": ["glockenspiel"], "-3.0 0.5 13.0": ["nila"], "11.4 12.6 15.4": ["porthole"], "-0.2 6.8 5.5": ["bismuth"], "8.4 -0.6 10.6": ["dissections"], "10.4 -3.1 9.7": ["citys"], "18.2 11.3 21.5": ["mossy"], "11.1 17.2 3.5": ["hunkered"], "-1.7 3.2 8.7": ["refiling"], "-2.5 14.6 2.5": ["redistributive"], "-2.5 7.2 7.7": ["somatic"], "7.3 13.1 9.5": ["downloader"], "4.7 -3.7 -0.6": ["postive"], "1.5 12.5 -2.3": ["proscribe"], "-5.5 5.3 17.8": ["nonfederal"], "-1.0 -2.7 12.9": ["newbuildings"], "6.2 17.0 5.2": ["mercies"], "4.6 4.8 6.1": ["costarring"], "8.0 28.6 24.1": ["swordsman"], "15.4 7.8 6.0": ["infographic"], "2.9 -2.8 13.4": ["digesters"], "-2.1 5.8 5.7": ["ohm"], "3.1 13.1 8.9": ["gumshoe"], "-4.5 9.5 15.3": ["mixologists"], "-1.7 1.6 22.4": ["garnishing"], "3.8 6.3 3.5": ["dist"], "10.3 12.3 15.5": ["chav"], "-0.2 10.3 11.3": ["castmate"], "5.2 -3.6 5.9": ["committe"], "4.4 13.8 4.2": ["firebreak"], "3.1 3.2 17.5": ["quarried"], "-3.0 4.8 8.6": ["impressionism"], "4.6 -0.1 10.0": ["ae"], "7.8 4.8 2.8": ["unboxing"], "14.1 11.1 18.6": ["squire"], "1.9 -1.9 3.1": ["footbridges"], "-4.4 2.3 3.2": ["holidayed"], "4.8 20.8 11.8": ["sycophant"], "5.8 5.4 25.4": ["ganache"], "-0.4 12.1 11.1": ["dinning"], "2.4 16.3 13.0": ["hungers"], "6.8 6.0 7.6": ["revivalist"], "16.0 14.6 7.1": ["bigness"], "-14.0 4.5 3.0": ["nominators"], "4.1 15.2 7.4": ["viceroy"], "-12.4 10.1 8.3": ["deplane"], "3.9 5.3 6.3": ["couplers"], "6.3 8.0 14.0": ["plungers"], "-2.8 4.1 2.9": ["hyperthyroidism"], "-0.7 13.2 6.3": ["filmdom"], "2.2 10.4 31.0": ["repast"], "16.5 10.1 13.1": ["clank"], "1.6 2.5 5.6": ["spiritualist"], "0.5 3.4 25.7": ["ova"], "6.8 6.0 14.3": ["solon"], "5.7 -9.2 -3.6": ["amex"], "1.5 5.5 6.3": ["backrest"], "4.7 -0.9 1.5": ["franked"], "-5.1 6.6 18.1": ["cremains"], "4.6 -7.8 1.2": ["letterheads"], "1.0 12.3 10.4": ["tularemia"], "-2.2 15.1 4.2": ["countenanced"], "2.0 1.7 5.7": ["amelioration"], "1.5 -0.1 6.0": ["septet"], "-5.0 9.9 13.2": ["itemizing"], "-0.8 3.4 12.1": ["hashes"], "23.7 10.6 18.9": ["legless"], "4.8 4.8 -4.2": ["collates"], "16.0 11.6 -1.2": ["earthshaking"], "4.1 23.0 7.1": ["oppresses"], "18.3 25.1 13.4": ["specters"], "1.9 11.0 -2.3": ["conflating"], "0.3 -1.5 11.8": ["powwows"], "3.7 11.2 30.2": ["boatmen"], "1.2 12.7 2.2": ["blabbing"], "-1.2 8.9 30.0": ["antipasti"], "20.1 6.9 14.3": ["totemic"], "-5.0 -0.8 -4.4": ["coeducational"], "0.2 9.8 14.5": ["fruitcakes"], "1.0 20.7 9.9": ["egoism"], "8.9 21.1 5.6": ["forefather"], "3.7 10.1 2.4": ["semiofficial"], "24.1 23.1 10.7": ["androids"], "8.9 10.8 10.2": ["loincloth"], "1.1 -5.4 12.1": ["lactating"], "-1.7 5.4 1.5": ["conveyances"], "-1.7 9.1 4.6": ["airdate"], "-4.4 2.4 3.9": ["osteopath"], "-1.7 13.1 29.8": ["dredgers"], "11.1 12.5 11.2": ["glassing"], "5.6 21.2 3.5": ["regenerates"], "13.0 13.3 9.9": ["bejesus"], "11.5 24.9 10.2": ["unmercifully"], "13.6 12.2 17.9": ["sheepdog"], "10.3 2.3 6.0": ["crated"], "-1.5 5.6 8.2": ["camshaft"], "0.6 12.9 21.8": ["rutting"], "6.8 37.6 3.5": ["disbelievers"], "-7.0 5.2 8.7": ["gins"], "-2.8 -0.4 5.2": ["mitigations"], "9.9 -3.2 6.3": ["loitered"], "8.6 8.9 12.4": ["thinkin"], "-3.6 -0.7 17.4": ["newbuilding"], "0.9 1.9 11.1": ["woodcuts"], "-1.6 0.8 6.7": ["microspheres"], "14.9 2.7 13.0": ["hardhats"], "-5.7 31.9 9.5": ["battlespace"], "-0.7 15.5 -4.6": ["misinform"], "23.6 5.7 14.0": ["muppet"], "9.6 13.8 21.7": ["bruisers"], "10.6 22.8 13.4": ["toady"], "-0.7 15.5 10.3": ["biathlete"], "-9.1 3.6 3.2": ["halachic"], "0.1 7.8 8.9": ["phenotypic"], "-4.1 -0.6 11.4": ["scrapie"], "3.4 14.2 -0.4": ["unserious"], "-3.8 1.8 12.3": ["carburetors"], "-12.9 8.6 1.0": ["millages"], "0.7 9.2 12.0": ["hydroplane"], "4.6 10.0 2.3": ["concertgoer"], "-3.3 9.5 2.3": ["cabriolet"], "0.8 -0.6 -1.0": ["decison"], "14.0 10.3 1.3": ["blots"], "6.2 13.2 10.2": ["beseech"], "7.6 15.8 11.6": ["inoculating"], "7.1 15.6 13.2": ["dopers"], "-2.8 16.3 8.6": ["federalists"], "8.9 7.0 38.5": ["escargot"], "-0.6 18.6 9.1": ["ciphers"], "3.4 12.9 5.6": ["brushfire"], "0.6 8.8 2.3": ["endline"], "2.4 10.0 20.0": ["veining"], "2.1 10.3 15.3": ["aspens"], "-3.3 9.6 11.2": ["casualness"], "12.5 17.3 9.6": ["swarthy"], "8.7 -1.1 23.5": ["cookoff"], "0.3 5.5 -0.1": ["terahertz"], "10.4 4.1 13.8": ["demi"], "4.7 5.5 9.2": ["cbank"], "3.3 -2.1 36.2": ["tortellini"], "-3.0 16.5 1.7": ["barracking"], "-7.6 1.8 -0.7": ["availabilities"], "0.9 11.4 15.5": ["heuristic"], "14.3 -4.9 5.5": ["multiphase"], "10.8 12.3 9.2": ["beaning"], "12.8 -2.0 4.3": ["upsized"], "-3.7 5.6 -0.6": ["printings"], "10.7 15.7 2.5": ["orifices"], "4.0 10.5 5.6": ["impermissibly"], "-6.6 4.8 2.9": ["benzodiazepine"], "18.1 22.0 8.3": ["trembles"], "1.3 4.7 9.6": ["hereof"], "4.3 5.9 3.1": ["preordered"], "2.8 17.2 12.1": ["masochist"], "1.6 10.3 0.2": ["hellos"], "-0.3 15.9 5.5": ["countercharges"], "1.5 11.5 4.7": ["tinder"], "11.8 -0.6 -0.1": ["floorspace"], "2.7 5.6 9.0": ["balladry"], "-4.0 3.3 9.4": ["unrehearsed"], "12.1 4.5 1.1": ["photofinishing"], "-0.3 8.9 9.2": ["envies"], "1.8 17.3 -0.8": ["inheritor"], "-9.3 3.6 5.7": ["strictness"], "13.2 12.3 -4.7": ["inconspicuously"], "14.2 15.6 11.4": ["baleful"], "-0.2 21.5 7.7": ["sanctify"], "-4.3 26.7 5.8": ["lashkar"], "-5.9 5.5 14.1": ["euthanization"], "-3.6 4.4 9.3": ["purebreds"], "19.5 27.4 6.4": ["bogeymen"], "-2.9 12.7 5.1": ["tiebreaks"], "3.3 7.3 12.2": ["cooktop"], "10.6 10.2 5.1": ["govts"], "0.7 2.1 7.5": ["instated"], "1.0 11.5 5.7": ["phosphor"], "-1.4 1.2 0.7": ["razzed"], "4.1 20.8 19.9": ["cutlass"], "11.4 12.5 13.2": ["vomits"], "5.2 5.1 14.2": ["ku"], "12.5 1.8 9.7": ["spruces"], "3.4 19.0 6.0": ["tamil"], "-12.1 -2.3 1.8": ["nephrologist"], "12.8 3.1 18.5": ["claymation"], "-9.7 1.9 4.7": ["interworking"], "-4.3 9.0 8.7": ["sidemen"], "-0.4 4.6 -6.8": ["interveners"], "9.2 11.1 15.8": ["queasiness"], "0.2 3.9 10.2": ["brights"], "7.1 0.3 8.2": ["dah"], "3.1 1.6 -0.1": ["diastolic"], "5.8 17.1 1.8": ["mown"], "5.2 6.4 4.6": ["managerless"], "-3.5 6.9 2.3": ["prepaying"], "10.0 -0.8 5.5": ["lorded"], "9.6 11.4 28.8": ["dredger"], "-2.3 5.0 9.0": ["alendronate"], "7.8 13.2 6.4": ["powerbase"], "-7.8 4.6 15.7": ["psilocybin"], "0.8 1.5 2.9": ["polyphonic"], "-11.2 -0.6 1.2": ["guested"], "-0.3 3.8 -2.1": ["retuning"], "13.0 9.0 12.7": ["quizzically"], "5.1 26.8 -0.5": ["wittingly"], "-3.2 -3.2 10.0": ["hydrochloride"], "-4.6 13.7 7.0": ["serotypes"], "5.9 -4.1 11.5": ["bodegas"], "0.5 14.6 13.3": ["chit"], "4.4 -2.7 -3.7": ["extention"], "15.9 7.6 8.3": ["jingling"], "7.6 6.7 18.1": ["dogsled"], "3.5 16.9 9.5": ["ratting"], "1.6 0.6 7.4": ["preemie"], "6.9 3.9 9.8": ["reiki"], "-7.7 9.9 3.7": ["underbanked"], "-1.2 3.2 12.0": ["silicification"], "12.4 22.1 16.3": ["damsels"], "9.2 -5.9 8.7": ["subsisted"], "15.9 6.7 22.3": ["drippy"], "22.3 10.6 9.1": ["girds"], "11.6 10.6 -1.0": ["inroad"], "5.9 4.6 5.9": ["monoline"], "12.1 20.8 4.7": ["inconveniently"], "-1.4 9.6 24.1": ["locavore"], "14.7 25.4 8.4": ["commies"], "0.4 13.6 20.0": ["skunked"], "5.3 6.2 11.0": ["hangin"], "4.9 -1.3 7.0": ["dei"], "8.8 0.7 7.9": ["lowercase"], "16.0 10.6 9.3": ["defensives"], "-4.5 1.1 0.9": ["presbyteries"], "5.2 1.5 5.4": ["underperforms"], "4.2 0.9 14.8": ["trad"], "14.1 9.3 14.5": ["bioengineered"], "11.5 7.0 10.4": ["cockamamie"], "1.1 -0.3 9.6": ["mipomersen"], "12.7 5.2 -3.0": ["dd"], "-1.1 8.7 13.9": ["humored"], "-8.7 2.6 7.8": ["hygienists"], "26.0 7.5 1.4": ["acquistion"], "3.1 8.8 7.8": ["guideposts"], "0.2 7.6 7.7": ["coupler"], "-2.1 9.0 9.8": ["vasculature"], "-2.5 -2.4 2.7": ["recertify"], "4.3 8.3 3.1": ["wrings", "demodulated"], "2.0 8.5 14.8": ["waterskiing"], "-2.9 15.7 -1.1": ["micromanaged"], "25.2 3.4 8.9": ["infotech"], "9.3 -0.3 4.9": ["toxicologists"], "-3.1 3.1 12.2": ["hoppy"], "4.9 -2.9 9.7": ["sheetmetal"], "3.3 21.8 9.6": ["unguided"], "7.4 17.8 3.7": ["ignorantly"], "12.6 0.6 17.4": ["pompadour"], "11.2 18.3 13.1": ["oligarchic"], "-0.7 24.1 8.1": ["humanness"], "3.5 31.9 -0.8": ["airbases"], "-0.9 8.4 6.2": ["callout"], "-6.0 5.0 4.1": ["immunosuppressive"], "-0.2 10.1 11.0": ["croplands"], "4.6 -0.1 -1.8": ["sweltered"], "13.6 8.0 14.9": ["rigger"], "2.6 1.4 19.7": ["nelson"], "-1.5 13.6 5.7": ["upperhand"], "-13.7 6.2 8.4": ["siad"], "15.2 16.1 12.9": ["wordlessly"], "-2.9 10.6 7.2": ["nays"], "10.4 4.9 28.8": ["dippers"], "16.0 15.6 5.5": ["speedo"], "13.4 2.4 9.8": ["lineswoman"], "-0.1 4.6 2.5": ["legspinner"], "-6.9 4.5 5.4": ["hydrofracking"], "6.9 15.2 11.2": ["confederacy"], "6.8 9.0 31.7": ["hoagie"], "4.5 5.6 4.6": ["bridled"], "4.7 15.3 1.9": ["uncontained"], "3.7 1.7 2.4": ["flavanols"], "4.6 6.6 2.6": ["churchman"], "-3.0 -1.6 5.6": ["placental"], "8.1 1.7 7.3": ["concertina"], "7.7 13.0 9.7": ["knifes"], "9.1 9.0 12.4": ["indiscernible"], "0.9 1.7 6.5": ["reinsertion"], "-7.3 15.9 8.6": ["wittiest"], "-3.8 2.0 -3.9": ["appreciations"], "4.2 11.8 8.5": ["recidivist"], "4.7 0.6 8.2": ["newsmagazines"], "18.6 -1.8 -3.7": ["pl"], "11.3 6.2 9.4": ["hovel"], "6.1 22.5 10.1": ["inertial"], "3.3 6.6 3.1": ["pensionable", "deglamorized"], "-2.4 4.6 8.2": ["lodgers"], "6.4 5.4 4.7": ["boldface"], "1.0 10.9 15.3": ["kami"], "9.3 8.1 20.0": ["goblets"], "6.5 3.3 13.7": ["bollard"], "0.7 4.3 9.1": ["worthies"], "0.8 12.0 4.3": ["xvii"], "7.3 15.2 13.0": ["annulus"], "-8.0 10.4 5.1": ["aphasia"], "4.8 7.2 33.8": ["radicchio"], "3.6 13.2 8.3": ["qi"], "5.5 15.5 22.3": ["houseplant"], "-6.8 8.9 -0.1": ["compensable"], "9.0 11.2 9.7": ["existences"], "3.0 -4.7 10.8": ["vasectomies"], "3.1 14.6 6.7": ["senselessness"], "14.3 10.3 30.1": ["newts"], "3.5 1.3 13.8": ["nordic"], "6.8 2.7 2.0": ["peals"], "-14.9 3.9 5.7": ["comorbidity"], "-6.5 4.2 2.2": ["rostering"], "-7.2 1.2 8.9": ["nonsurgical"], "2.0 4.0 -0.9": ["resounds"], "-9.0 2.5 3.2": ["stringency"], "7.1 14.7 18.8": ["unpleasantly"], "-3.2 24.3 2.7": ["propagandistic"], "6.1 14.6 14.3": ["pouts"], "8.0 6.9 11.6": ["tingly"], "2.0 15.3 3.0": ["toggling"], "6.7 1.2 4.4": ["ntl"], "6.6 2.9 8.5": ["ubuntu"], "-0.6 4.8 12.1": ["pothead"], "8.4 8.5 5.4": ["cn"], "2.9 18.8 -2.6": ["unsecure"], "2.9 -1.5 6.9": ["benchtop"], "10.3 10.0 29.4": ["chopstick"], "1.9 8.2 8.9": ["lamentations"], "7.1 3.7 2.2": ["publicizes"], "5.5 9.5 12.2": ["proscenium"], "4.1 2.6 4.5": ["newsagency"], "-6.5 12.3 9.0": ["stager"], "9.0 8.9 4.9": ["fireballer"], "-1.3 11.7 -2.2": ["fatiguing"], "11.0 9.8 8.5": ["inbetween"], "-1.6 9.4 5.0": ["censures"], "3.7 12.5 13.3": ["ritualized"], "4.1 22.4 18.0": ["crewmate"], "1.1 6.9 3.4": ["inappropriateness", "iclaprim", "finsih"], "1.1 3.6 9.6": ["liposomes"], "12.6 15.5 7.5": ["outmuscle"], "13.5 5.7 8.4": ["backdown"], "-5.6 4.6 5.4": ["thalamus"], "8.4 25.1 21.4": ["varmints"], "-3.5 7.0 -0.4": ["internalizing"], "19.7 4.3 -2.1": ["instal"], "-1.5 1.5 18.6": ["stemware"], "-5.8 13.7 6.4": ["affability"], "3.2 6.6 11.7": ["zaniness"], "7.5 1.2 15.9": ["trebles"], "8.2 19.7 7.3": ["recoils"], "2.8 3.5 13.5": ["jacketed"], "18.9 3.1 7.1": ["megacity"], "-3.5 -1.8 -0.1": ["couriered"], "10.0 5.4 8.7": ["megacities"], "2.0 10.9 5.8": ["exorcisms"], "-4.5 9.6 9.7": ["cinephiles"], "1.0 -3.7 13.4": ["particleboard"], "7.0 22.3 11.1": ["transgressors"], "-0.2 5.2 30.2": ["camellia"], "-4.3 4.6 10.1": ["microdermabrasion"], "6.9 11.6 8.2": ["agoraphobia"], "7.7 0.7 16.7": ["chun"], "5.2 13.3 2.3": ["medias"], "11.2 3.6 10.0": ["stunners"], "6.6 3.8 13.1": ["seamed"], "15.9 16.0 17.5": ["entangling"], "1.1 0.7 13.6": ["sundresses"], "11.9 8.5 24.9": ["sumac"], "-4.8 2.3 0.0": ["approvable"], "-4.4 24.4 6.1": ["naxalite"], "10.5 -2.0 10.0": ["relisted"], "4.5 10.3 2.2": ["guage"], "12.3 10.2 14.0": ["hoofs"], "5.3 16.5 -0.2": ["electrocutions"], "17.7 4.2 9.0": ["dutch"], "10.2 2.9 -1.6": ["tomography"], "6.9 20.5 12.6": ["ignoramus"], "7.6 12.2 12.3": ["copulation"], "9.7 13.7 15.0": ["portholes"], "2.7 0.8 4.0": ["tobe"], "8.6 4.6 18.5": ["carnation"], "-5.0 -3.0 -3.6": ["rifaximin"], "0.9 7.7 -3.5": ["percolates", "xxxi"], "-2.2 -2.2 9.1": ["osteonecrosis"], "10.0 4.5 4.2": ["discotheques"], "5.4 3.2 7.7": ["bloodmobile"], "5.0 3.2 39.2": ["molting"], "9.9 2.2 0.8": ["sashaying"], "-2.1 10.1 18.3": ["interbreeding"], "5.2 4.5 11.0": ["apothecary"], "-6.8 12.9 11.6": ["exfoliate"], "-1.3 10.6 10.5": ["federalization"], "13.4 6.3 7.1": ["redlining"], "-2.0 17.3 -0.4": ["harassments"], "-2.3 4.9 11.2": ["defrocking"], "4.0 8.2 6.2": ["cannily"], "10.6 6.3 17.3": ["unseasonal"], "8.2 0.8 5.9": ["hammed"], "9.9 7.2 10.4": ["sez"], "-2.5 35.6 -1.2": ["mujahedin"], "6.9 4.8 -2.1": ["assistive"], "7.5 2.1 -1.3": ["decreeing"], "5.0 24.2 3.0": ["unceasingly"], "-0.4 1.2 -2.4": ["nonusers"], "-1.8 -4.4 11.2": ["ug"], "6.1 5.5 17.9": ["steamboats"], "-5.0 11.5 6.5": ["regionalize"], "-8.9 2.6 6.7": ["preamp"], "16.2 7.7 4.6": ["gassy"], "10.6 6.7 8.6": ["dirtied"], "-2.9 4.7 4.7": ["naturopath"], "10.8 7.1 25.2": ["mullets"], "2.9 11.3 2.7": ["flagman"], "7.1 12.4 1.3": ["concomitantly"], "-6.4 6.8 -2.8": ["pastorate"], "3.9 -4.9 11.7": ["yun"], "11.4 5.2 7.7": ["askance"], "18.4 10.2 24.9": ["gerbil"], "-8.0 -2.7 21.9": ["vinegars"], "3.3 8.4 3.8": ["groundsmen"], "8.5 7.6 7.9": ["exe"], "9.4 3.8 35.6": ["gorgonzola"], "3.3 3.0 7.3": ["saccharin"], "10.1 6.5 10.2": ["bosoms"], "-0.7 13.9 4.0": ["secularized"], "7.6 7.0 6.2": ["groundstaff"], "6.5 19.4 15.5": ["plasmid"], "-0.1 14.7 -2.6": ["abrogating"], "5.2 -2.7 13.2": ["ladled"], "2.5 14.5 -1.7": ["avowedly"], "6.8 6.3 14.7": ["quartzite"], "11.2 5.6 9.3": ["dipstick"], "-3.1 7.3 15.7": ["woodlot"], "8.9 -2.1 1.1": ["sonograms"], "-0.2 0.7 0.2": ["rivaroxaban"], "11.8 20.8 7.8": ["gambits"], "24.3 5.0 8.3": ["plonked"], "7.7 -0.2 16.6": ["steppers"], "4.6 -2.8 4.0": ["rereleased"], "6.1 6.3 8.3": ["ranchland"], "3.5 -3.7 5.7": ["maxes"], "10.1 -2.6 4.5": ["duked"], "18.6 7.7 32.1": ["guano"], "-3.4 28.3 10.4": ["rejectionists"], "9.3 5.5 14.1": ["stickup"], "1.6 13.5 1.8": ["outbox"], "1.9 0.6 2.4": ["metabolomics"], "2.5 13.1 9.1": ["perplexity"], "10.4 7.5 12.8": ["nonevent"], "-0.0 1.1 9.1": ["unquoted"], "7.8 5.3 9.0": ["nacelle"], "8.1 17.1 13.1": ["unbalance"], "-4.3 8.3 1.4": ["construing"], "12.0 8.1 12.4": ["jammies"], "0.5 5.4 20.4": ["containerships"], "4.3 0.5 10.6": ["louche"], "2.4 9.5 5.7": ["bluffed"], "0.3 20.8 11.1": ["dialectical"], "-2.5 2.9 5.7": ["headspace"], "1.6 5.4 6.7": ["unidirectional"], "14.6 11.7 12.9": ["thwack"], "-1.9 10.3 10.7": ["determinate"], "-3.2 -1.1 6.3": ["backplanes"], "11.2 11.7 9.2": ["windiest"], "10.7 3.5 9.6": ["buckyballs"], "2.3 2.4 4.6": ["flunks"], "10.9 9.2 8.0": ["furrowed"], "8.3 17.4 7.9": ["iniquitous"], "6.2 13.8 5.0": ["frights"], "-3.0 7.4 8.3": ["freerolls"], "-5.1 11.5 4.6": ["teamsheet"], "3.1 7.6 10.5": ["earlobes"], "-0.9 7.4 5.5": ["bulleted"], "1.2 8.1 8.3": ["dacha"], "7.7 5.5 5.4": ["familar"], "9.4 10.7 7.4": ["intermixed"], "-0.2 8.0 12.1": ["handshaking"], "11.8 14.2 9.8": ["thuds"], "0.9 2.8 4.1": ["magnetometers"], "9.0 4.5 3.5": ["seamy"], "6.8 13.3 0.0": ["reverberation"], "4.6 8.1 11.9": ["chatterbox"], "13.0 13.9 9.7": ["unsinkable"], "3.8 18.2 15.3": ["flyballs"], "3.5 9.5 -0.4": ["prioritises"], "-0.9 -1.7 5.4": ["reaccreditation"], "9.6 12.8 14.3": ["monosyllabic"], "2.9 -4.3 5.5": ["hairpins"], "-3.7 -7.3 1.7": ["revues"], "6.3 9.4 17.8": ["turtlenecks"], "9.2 10.7 33.5": ["gill"], "-0.8 12.1 9.2": ["wearisome"], "4.2 14.8 8.8": ["pseudoscience"], "10.4 12.8 7.6": ["collusive"], "15.1 18.1 6.8": ["sicko"], "-7.0 12.5 14.6": ["histogram"], "-1.5 3.6 16.0": ["chinos"], "13.4 6.9 4.7": ["commoditised"], "1.6 5.0 28.8": ["poundage"], "7.3 11.6 9.3": ["existentialism"], "-1.0 -1.0 15.1": ["hairpieces"], "-0.2 26.3 4.5": ["unhesitatingly"], "-0.4 26.9 15.5": ["ballcarrier"], "-3.7 7.0 12.7": ["winterized"], "5.2 13.1 10.9": ["darndest"], "6.7 5.2 15.1": ["tine"], "8.2 5.8 17.1": ["marigold"], "5.5 -1.5 17.6": ["curio"], "15.5 5.0 8.9": ["thickener"], "12.4 9.3 10.1": ["disparagingly"], "11.7 17.4 8.2": ["unfortunates"], "-1.5 13.2 4.9": ["overanalyze"], "1.9 0.4 5.8": ["octet"], "-0.0 3.5 1.3": ["adjustability"], "10.0 18.2 19.6": ["flotillas"], "6.9 8.1 3.0": ["undoes"], "1.5 17.8 3.5": ["disparages"], "6.3 -6.5 11.1": ["stocker"], "14.7 15.5 12.2": ["steeds"], "16.0 14.0 25.5": ["herbivore"], "6.8 22.5 4.0": ["jews"], "15.0 20.5 2.1": ["unquenchable"], "3.3 3.9 10.8": ["seltzer"], "13.8 4.7 6.2": ["charmless"], "-1.6 5.9 7.2": ["fallouts"], "15.6 3.5 11.4": ["tarry"], "4.7 1.3 1.8": ["televison"], "10.3 5.6 13.3": ["microstructure"], "8.8 12.1 5.2": ["faints"], "-3.1 10.1 3.2": ["hitout"], "20.0 3.4 20.3": ["roo"], "9.7 10.2 3.6": ["abstruse"], "-0.1 1.0 9.1": ["caucasian"], "1.1 15.8 18.9": ["yorkers"], "-3.5 7.9 9.1": ["friending"], "4.1 4.5 11.9": ["volcanism"], "3.9 2.6 19.4": ["wainscoting"], "-1.2 3.3 8.7": ["staycations"], "4.9 16.5 3.1": ["dozers"], "1.5 9.0 11.3": ["tentativeness"], "7.4 2.3 10.0": ["elastomer"], "4.6 12.4 3.0": ["ngmoco"], "9.8 5.5 5.6": ["mach"], "1.8 14.5 17.6": ["caisson"], "5.4 8.9 2.0": ["bidet"], "9.2 12.8 -0.2": ["coincidently"], "18.2 10.8 12.8": ["mamma"], "-0.2 11.8 2.1": ["lacuna"], "5.9 17.2 0.8": ["epochs"], "5.5 2.3 42.9": ["scallion"], "11.2 15.4 2.7": ["telegraphs"], "7.7 11.4 7.0": ["artificiality"], "0.9 9.2 9.5": ["guernsey"], "4.1 18.6 0.9": ["recapitalizing"], "15.5 -3.3 11.3": ["stacker"], "15.2 -2.8 8.8": ["bopped"], "-0.9 -1.7 4.6": ["talkshow"], "6.7 9.3 6.6": ["disproportional"], "3.0 -1.7 16.4": ["sulphate"], "0.7 6.6 18.8": ["minicars"], "-5.4 0.5 1.0": ["paroxetine"], "-2.8 3.3 7.5": ["multiplexer"], "-1.9 5.0 13.2": ["carafe"], "-2.6 9.6 3.8": ["caucusing"], "6.5 0.2 5.6": ["necropolis"], "7.5 6.2 3.4": ["preternaturally"], "8.1 21.9 1.4": ["inquisitors"], "2.6 12.7 0.9": ["eyestrain"], "-8.2 4.9 4.5": ["neonatologist"], "-2.1 7.9 14.4": ["gelded"], "5.3 -0.1 7.9": ["sparky"], "2.1 19.4 15.8": ["depredation"], "4.5 2.4 -3.2": ["dimed"], "-2.8 1.1 0.9": ["infromation"], "9.3 4.5 -1.1": ["divison"], "0.1 3.2 -0.0": ["polyclinic"], "2.5 8.2 13.3": ["languorous"], "2.6 9.1 -0.2": ["shopworn"], "-1.1 3.6 7.2": ["sportswomen"], "19.1 13.4 48.8": ["cuttlefish"], "2.5 3.0 17.6": ["cockfights"], "-2.1 0.0 8.2": ["gestational"], "16.3 10.9 17.2": ["unhook"], "7.5 2.0 7.5": ["cumbia"], "-3.5 11.2 16.3": ["middie"], "4.4 10.9 1.0": ["fansite"], "13.1 1.8 6.0": ["shimmered"], "2.0 -0.4 10.3": ["giveback"], "-8.4 10.4 11.2": ["pluripotent"], "4.3 6.8 4.9": ["bein"], "3.3 9.1 11.7": ["quinella"], "21.4 4.7 26.2": ["sandcastle"], "1.8 5.8 8.4": ["thre"], "-2.4 16.9 7.4": ["pollens"], "4.9 12.2 30.2": ["breakwaters"], "7.2 16.8 0.5": ["quintessence"], "-4.9 4.6 18.8": ["sila"], "12.5 -3.8 4.9": ["atwitter"], "3.0 20.2 13.1": ["morrow"], "10.5 6.5 13.4": ["cornhole"], "-8.3 2.7 1.7": ["adhesions"], "7.6 8.7 23.3": ["mosses"], "3.2 13.1 8.4": ["underreport"], "8.8 5.7 8.2": ["mindboggling"], "1.3 2.2 6.5": ["preggers"], "-2.0 3.0 12.4": ["abayas"], "0.1 22.6 -3.0": ["disgracing"], "2.9 16.0 2.7": ["scuffs"], "6.0 20.2 7.3": ["ruffians"], "9.2 4.1 7.8": ["exabytes"], "14.9 4.9 18.9": ["splashdown"], "-5.0 -0.1 20.8": ["standardbred"], "-4.3 -0.7 1.6": ["summations"], "-2.4 0.4 -6.0": ["hemodynamic"], "-3.9 3.8 14.8": ["eyeshadow"], "3.2 26.2 9.9": ["deceives"], "7.8 15.8 8.2": ["commentariat"], "-11.5 5.9 6.3": ["catechesis"], "-0.2 3.6 9.2": ["punchouts"], "9.5 13.6 12.1": ["wreaks"], "-6.0 6.6 4.2": ["caries"], "2.7 17.4 10.0": ["absolutism"], "8.5 3.8 4.2": ["singalongs"], "20.3 8.6 8.7": ["whirls"], "9.8 8.1 9.8": ["flimsiest"], "7.6 6.1 20.3": ["goulash"], "3.5 -0.7 25.6": ["inchers"], "-16.5 9.2 2.2": ["anthracycline"], "-7.4 5.7 10.8": ["stagers"], "18.9 9.7 7.4": ["slunk"], "6.4 9.9 13.1": ["tranquilize"], "2.2 17.4 8.5": ["inviolate"], "-7.4 12.0 8.3": ["thana"], "-6.7 1.3 1.5": ["copayment"], "-1.4 14.4 14.9": ["monarchical"], "2.9 10.6 2.8": ["notionally"], "4.1 6.5 5.7": ["upswings"], "1.1 -3.9 -2.0": ["shortlisting"], "6.3 0.2 6.9": ["onesies"], "-3.1 -1.0 5.1": ["bedroomed"], "-0.6 7.5 36.8": ["largemouths"], "4.4 10.6 18.3": ["hanky"], "-1.3 -7.0 -2.0": ["bursar"], "7.6 4.5 2.1": ["forebear"], "-0.7 -1.2 5.1": ["progeria"], "12.4 15.4 12.3": ["disdainfully"], "6.0 2.4 4.4": ["ostentation"], "9.4 19.1 6.7": ["seige"], "4.2 11.0 10.6": ["transience"], "8.5 18.0 6.8": ["chakra"], "13.8 14.9 11.0": ["crouches"], "-6.7 8.1 5.8": ["undersecretaries"], "4.5 1.6 5.3": ["scorekeepers"], "2.0 4.3 5.5": ["indolence"], "-4.3 4.8 6.9": ["mucosal"], "4.1 10.0 12.0": ["bachelorettes"], "0.7 22.0 6.3": ["israel"], "-6.9 13.3 5.9": ["lamentation"], "10.5 13.2 8.2": ["ossified"], "1.1 11.4 13.6": ["insouciant"], "-3.4 -2.3 -3.7": ["mifepristone"], "8.4 7.4 6.7": ["fuzzier"], "-2.4 12.0 12.7": ["exfoliating"], "3.0 10.1 22.7": ["umami"], "5.5 0.4 1.8": ["petabyte"], "2.0 5.6 16.0": ["stockwork"], "18.4 18.2 16.9": ["banshee"], "-3.5 8.8 5.6": ["impasses"], "9.2 -6.2 11.4": ["neodymium"], "17.6 6.7 14.3": ["animatronics"], "16.4 8.3 33.2": ["sculpin"], "8.1 6.1 4.1": ["cosseted"], "11.1 6.8 12.6": ["millionths"], "9.0 16.2 11.1": ["lowliest"], "13.5 1.7 8.2": ["funnies"], "1.1 0.4 2.2": ["uncollectable"], "13.0 10.8 15.1": ["merest"], "10.2 14.2 2.5": ["counterfeiter"], "7.2 13.5 8.3": ["treed"], "-3.8 1.8 0.3": ["teleradiology"], "-1.5 12.8 5.2": ["worrier"], "12.0 9.7 11.6": ["donnybrook"], "4.9 9.8 9.8": ["remapping"], "14.1 4.6 15.1": ["protrusions"], "-3.2 16.2 18.2": ["concubine"], "1.5 9.2 2.2": ["liftgate"], "-0.9 1.8 7.1": ["splices"], "18.8 19.4 9.2": ["protectionists"], "20.5 16.9 5.9": ["cretins"], "-3.0 7.3 5.7": ["taluks"], "8.6 15.7 9.4": ["sagely"], "-0.6 -2.4 10.0": ["pointe"], "3.7 3.1 9.6": ["exoticism"], "-0.2 -1.9 14.8": ["rowhouses"], "4.4 13.0 17.4": ["niggas"], "-1.2 -0.1 7.6": ["gallium"], "-4.2 3.3 15.4": ["microarchitecture"], "-5.8 5.5 10.8": ["lama"], "4.0 14.2 6.2": ["existentialist"], "2.3 9.8 3.8": ["moonroof"], "2.2 7.8 2.0": ["gallivanting"], "-0.6 15.9 7.5": ["conceits"], "1.6 17.5 5.4": ["unobserved"], "7.2 1.7 13.8": ["refloated"], "-1.1 7.4 11.4": ["atypically"], "5.4 3.7 10.1": ["jerry"], "3.4 1.7 7.3": ["crystallizes"], "2.2 4.0 13.2": ["congas"], "10.1 -5.5 6.7": ["tres"], "-6.8 -2.7 16.0": ["polos"], "2.0 22.6 5.3": ["ruses"], "12.2 7.2 11.4": ["warchest"], "7.6 -1.9 10.2": ["dell"], "8.3 11.9 7.0": ["expropriating"], "6.2 14.3 12.0": ["testily"], "10.2 12.1 11.3": ["abseil"], "11.5 6.1 1.9": ["switchboards"], "4.2 10.4 7.6": ["centreman"], "4.6 6.5 16.3": ["aborigines"], "28.3 4.2 12.0": ["kiddy"], "-0.6 8.1 0.1": ["honeymooned"], "14.5 9.2 1.6": ["effusively"], "18.6 2.0 -5.2": ["foraying"], "10.0 5.2 11.8": ["whammy"], "-1.1 13.1 8.6": ["underprepared"], "-2.7 9.9 4.7": ["sidefoot"], "2.8 32.9 9.4": ["humvees"], "7.2 6.0 9.9": ["oversexed"], "9.8 12.6 9.2": ["perv"], "4.7 20.0 7.9": ["unspeakably"], "7.9 13.9 5.2": ["gladness"], "-0.4 12.5 14.2": ["senescence"], "3.8 11.4 8.3": ["tenses"], "13.8 7.2 1.7": ["frictionless"], "12.0 8.4 12.6": ["nerveless"], "-13.2 6.9 2.6": ["priors"], "-5.8 2.2 -0.6": ["postoperatively"], "9.5 0.1 3.7": ["cl"], "12.4 1.9 1.8": ["merchandizing"], "0.2 12.1 8.2": ["overemphasis"], "-6.3 1.9 3.3": ["creatinine"], "16.1 15.1 9.6": ["bozos"], "7.1 6.0 7.3": ["lovestruck"], "4.7 6.7 18.6": ["caterwauling"], "7.3 3.5 24.7": ["pierogi"], "9.5 6.8 8.6": ["surmounting"], "-2.8 2.7 20.6": ["violas"], "10.8 19.6 8.3": ["dolt"], "2.5 5.9 4.3": ["unreimbursed"], "9.3 7.5 7.1": ["competion"], "9.8 16.1 13.8": ["ignominiously"], "-0.8 0.2 -5.9": ["audiologists"], "7.1 7.7 9.8": ["dually"], "2.6 33.4 3.7": ["bombardier"], "-0.3 1.7 6.4": ["newsgroup"], "4.2 15.5 3.9": ["browbeaten"], "-4.9 -1.7 15.9": ["allograft"], "0.4 13.1 -3.9": ["badmouth"], "15.2 -3.1 9.7": ["beakers"], "8.9 3.3 11.1": ["ey"], "10.8 4.4 7.8": ["ahhs"], "5.9 13.0 5.2": ["proliferates"], "9.7 -0.1 5.0": ["ogled"], "-3.6 19.2 16.4": ["preposition"], "10.7 18.1 3.9": ["nonentity"], "22.3 7.5 8.2": ["creaked"], "9.4 9.1 12.7": ["paunchy"], "1.7 8.7 3.8": ["wr"], "11.8 13.9 0.6": ["unimagined"], "4.6 11.2 40.5": ["plovers"], "-1.3 4.1 8.5": ["schizophrenics"], "0.7 12.9 12.8": ["preciousness"], "12.4 6.6 6.7": ["relisting"], "-5.0 2.1 4.1": ["interweaves"], "11.9 5.3 7.8": ["epicenters"], "13.2 17.7 8.0": ["crackpots"], "-1.0 6.1 9.3": ["retweets", "maula"], "-4.2 9.3 18.7": ["herbaceous"], "3.0 1.6 5.7": ["somnolence"], "-10.6 7.1 3.0": ["infliximab"], "8.3 7.3 -4.3": ["founds"], "-3.6 9.8 6.1": ["recourses"], "10.6 9.5 5.8": ["vagabonds"], "-3.9 10.3 11.1": ["alkalinity"], "-0.9 5.5 9.7": ["bullfighters"], "-3.0 12.7 9.4": ["requesters"], "-1.2 6.0 6.1": ["essaying"], "7.7 12.4 6.5": ["unaligned"], "10.5 14.4 9.3": ["spasmodic"], "2.3 6.2 4.0": ["sadomasochistic"], "13.0 2.0 5.5": ["shaver"], "7.9 10.0 15.7": ["boozers"], "-2.4 9.1 2.8": ["prayerfully"], "0.2 27.7 10.0": ["vacillation"], "1.4 8.3 8.3": ["duffers"], "11.6 1.7 7.9": ["reinstallation"], "5.5 3.1 4.3": ["techy"], "-6.6 18.9 -0.9": ["apologetics"], "3.6 3.7 6.5": ["ageist"], "2.0 16.1 9.1": ["fibs"], "1.1 5.6 13.4": ["coffeeshop"], "6.6 4.5 4.8": ["sidings"], "5.2 9.0 -0.3": ["invigorates"], "3.8 1.1 33.5": ["deckhands"], "8.0 3.7 15.5": ["litho"], "8.4 0.5 7.7": ["sloughed"], "-1.4 3.1 11.3": ["cosmeceutical"], "3.7 7.0 13.5": ["befuddlement"], "12.0 13.5 28.7": ["starling"], "-4.6 2.8 4.3": ["oboist"], "11.3 13.5 12.4": ["primitives"], "13.3 -0.9 13.5": ["fen"], "-5.2 2.9 1.1": ["travail"], "20.0 2.1 11.1": ["fantasia"], "5.6 21.4 4.2": ["wingnut"], "1.1 9.5 9.5": ["vacillate"], "1.7 2.6 2.5": ["remonstrated"], "-6.2 7.4 -5.9": ["transferrable"], "-4.9 12.5 -6.1": ["federalized"], "6.8 10.8 16.0": ["aerator"], "-0.4 6.5 4.6": ["titlists"], "4.6 12.0 9.1": ["espressos"], "1.0 20.8 12.5": ["impermanence"], "-3.2 9.8 3.3": ["mentee"], "-8.7 8.7 4.0": ["demurs"], "0.7 6.1 13.5": ["photolithography"], "2.2 11.0 8.9": ["oversimplifying"], "9.9 5.1 7.4": ["puffery"], "-6.9 1.3 1.5": ["fundings"], "1.6 9.0 19.6": ["leaven", "globosa"], "5.2 0.2 2.6": ["sashay"], "4.9 -3.2 -3.0": ["trilingual"], "4.2 14.3 3.8": ["objectified"], "5.4 -2.1 15.2": ["overdressed"], "-0.4 12.4 9.2": ["skillset"], "7.6 8.3 0.9": ["hemorrhaged"], "3.6 6.6 10.4": ["bicoastal"], "6.1 13.4 4.0": ["wheelies"], "7.5 3.4 0.8": ["drainpipe"], "0.2 10.3 10.3": ["bioremediation"], "-5.1 6.1 5.3": ["dimmers"], "-4.1 13.8 4.5": ["mannerism"], "4.3 6.2 16.9": ["solons"], "15.8 -3.0 10.0": ["dia"], "18.1 21.0 12.8": ["unmoving"], "9.8 2.7 0.1": ["signficant"], "2.7 -1.4 14.5": ["multiday"], "13.1 3.7 10.2": ["resurging"], "-5.7 6.5 5.9": ["renovators"], "6.8 15.7 7.9": ["bedevils"], "7.8 4.6 13.4": ["patisserie"], "2.0 6.8 30.7": ["cutlets"], "9.7 -3.7 4.5": ["smocks"], "-4.2 14.2 5.6": ["masjid"], "-1.5 1.1 -3.4": ["unabridged"], "3.1 5.2 16.6": ["chondroitin"], "-0.9 0.9 -0.8": ["bikeways"], "0.2 -1.5 13.8": ["dairyman"], "0.2 8.9 7.4": ["stepbrothers"], "1.7 0.9 6.9": ["recessing"], "15.8 2.3 7.6": ["lenticular"], "-1.8 0.8 3.3": ["unbilled"], "4.7 9.0 5.1": ["glasnost"], "-5.2 -2.0 1.6": ["thermoplastics"], "5.6 2.1 34.6": ["fishmongers"], "2.7 0.5 7.6": ["elastomers"], "2.8 11.3 6.2": ["discontinuous"], "-3.5 6.7 13.4": ["arginine"], "0.6 7.3 9.4": ["pinhole"], "5.8 12.2 12.8": ["magnetosphere"], "15.3 14.7 22.5": ["bucketful"], "4.3 -0.3 19.0": ["coif"], "5.8 7.3 9.0": ["countdowns"], "5.5 -4.2 2.4": ["speechmaking"], "-10.1 -1.4 5.3": ["synopses"], "0.9 11.9 5.8": ["chastening"], "3.8 11.6 13.0": ["interrelationships"], "8.5 -5.6 7.5": ["quirkier"], "-2.6 3.3 12.0": ["pawnbrokers"], "-1.2 2.9 9.1": ["spankings"], "-4.2 4.6 12.3": ["agriculturists"], "-4.1 4.1 3.4": ["remarrying"], "13.0 2.1 15.9": ["puckered"], "-1.9 3.1 5.6": ["evaluable"], "-8.0 8.1 -3.5": ["immunogenic"], "11.2 -0.3 28.5": ["grapefruits"], "5.0 9.4 22.6": ["boxwood"], "-0.2 12.1 16.3": ["tailender"], "-4.8 8.6 5.3": ["citizenships"], "-3.4 10.1 10.2": ["congeniality"], "-10.2 8.0 16.3": ["rums"], "9.4 16.9 6.0": ["intoning"], "6.5 14.9 3.9": ["symbology"], "1.0 3.7 -2.7": ["reintroduces"], "-5.0 6.4 7.4": ["dermis"], "-4.6 3.8 6.5": ["subspecialties"], "13.0 17.6 33.7": ["whaler"], "11.0 -2.0 2.2": ["mgmt"], "3.7 -1.5 13.3": ["gouache"], "1.9 10.3 15.5": ["expressionistic"], "-3.3 14.6 16.1": ["stope"], "28.5 18.4 22.9": ["centipede"], "5.5 8.1 1.4": ["breathalyser"], "8.2 8.2 29.4": ["hulled"], "-2.4 6.5 6.7": ["frontliners"], "12.0 14.6 10.8": ["gripper"], "4.4 20.4 8.1": ["peaceniks"], "-4.8 -0.1 2.9": ["omnium"], "3.6 6.4 17.5": ["overripe"], "-10.1 -3.1 8.1": ["reoffer"], "27.4 27.9 21.1": ["beasties"], "-14.4 10.3 8.8": ["contextualize"], "-1.6 25.9 7.2": ["faithless"], "12.1 19.9 9.8": ["gruesomely"], "5.9 5.3 4.5": ["hawing", "gfx"], "-1.4 10.3 5.3": ["hallucinate"], "16.3 10.2 13.8": ["cliffside"], "5.1 1.9 7.5": ["deco"], "9.2 15.2 4.1": ["blindingly"], "2.7 17.9 11.2": ["mortification"], "22.6 18.7 22.5": ["anaconda"], "-1.6 -0.5 2.6": ["resubmitting"], "-3.9 4.3 0.1": ["reusability"], "11.5 5.5 48.2": ["barramundi"], "-3.0 -3.4 0.7": ["comparators"], "-5.0 9.7 15.1": ["recirculation"], "13.0 7.6 5.6": ["careens"], "8.6 6.8 6.2": ["ballcap"], "-4.4 9.2 9.2": ["honeys"], "-6.5 5.1 4.8": ["literatures"], "8.3 5.5 11.8": ["pantomimes"], "11.3 4.6 13.2": ["doleful"], "6.4 5.2 6.3": ["facsimiles"], "13.1 2.7 7.8": ["scuppering"], "8.6 6.6 2.9": ["ingests"], "1.4 1.6 12.4": ["ringette"], "19.9 11.7 3.3": ["spectaculars"], "6.4 8.0 11.4": ["busybodies"], "20.2 11.2 17.1": ["skittles"], "-1.8 12.3 -3.1": ["outrank"], "1.8 3.1 -1.1": ["keyless"], "9.6 4.3 7.2": ["skittle"], "5.2 20.4 9.1": ["sniveling"], "4.2 13.7 6.7": ["subhead"], "-12.5 8.5 1.5": ["evaluative"], "6.3 11.1 12.2": ["finessing"], "10.7 20.8 -0.3": ["superspy"], "8.8 16.1 9.0": ["decapitations"], "8.2 7.3 11.8": ["hed"], "12.0 10.7 8.1": ["linchpins"], "5.2 17.6 8.6": ["cueing"], "-6.2 23.4 17.5": ["defoliation"], "8.6 10.7 4.0": ["preternatural"], "2.1 25.3 9.0": ["feints"], "-0.8 0.0 20.4": ["alla"], "-0.7 4.1 8.6": ["viaducts"], "7.5 24.6 1.6": ["counterattacking"], "6.0 12.8 10.3": ["unhealthiest"], "-4.0 11.8 15.0": ["cuticles"], "0.9 20.5 7.5": ["roleplaying"], "-0.2 16.3 6.1": ["depopulated"], "-4.2 12.7 24.6": ["ryegrass"], "-2.4 15.0 4.7": ["militate"], "-6.7 5.2 6.6": ["omeprazole"], "3.6 6.0 10.9": ["dendrites"], "-6.3 5.5 8.9": ["weatherizing"], "11.9 2.1 11.6": ["arsed"], "8.6 7.8 15.3": ["gravedigger"], "12.4 7.3 12.2": ["hun"], "0.4 6.0 11.3": ["endothelium"], "12.1 -1.7 4.1": ["avec"], "15.1 2.7 18.7": ["streetside"], "11.2 13.7 8.2": ["distantly"], "1.8 9.7 21.1": ["zinnias"], "9.7 3.1 3.6": ["preened"], "5.9 6.9 8.5": ["caliper"], "-2.2 4.2 10.1": ["mopey"], "3.7 9.6 -7.2": ["contemporaneously"], "4.7 14.6 15.5": ["aerate"], "3.5 13.9 4.8": ["windchill"], "1.2 7.2 12.7": ["arpeggios"], "13.3 13.5 12.0": ["vestigial"], "3.4 14.4 15.2": ["photoreceptors"], "15.6 21.2 6.9": ["snatchers"], "8.7 -0.1 15.1": ["funerary"], "-0.9 7.5 6.5": ["netballers"], "8.2 4.1 8.5": ["superwoman"], "-1.3 13.7 7.9": ["gettable"], "-0.2 6.9 7.5": ["landslip"], "0.3 16.7 11.2": ["backspin"], "-0.8 5.9 10.4": ["rinses"], "0.3 10.8 1.3": ["financers"], "-3.3 14.1 4.0": ["demarche"], "8.1 -0.7 6.2": ["accessorised"], "4.9 3.1 12.8": ["palazzo"], "9.7 4.6 13.4": ["doddering"], "7.0 15.5 15.1": ["lowlifes"], "9.3 15.0 5.2": ["inextricable"], "18.3 8.5 5.0": ["listlessly"], "-6.9 3.1 8.5": ["passbook"], "10.7 16.8 16.3": ["omnivorous"], "0.1 9.7 1.8": ["trichlorethylene"], "3.0 2.1 -3.5": ["svp"], "8.4 11.4 3.7": ["trivialities"], "-3.1 9.7 6.4": ["begrudging"], "-7.9 12.6 0.4": ["ofcourse"], "-3.5 11.6 21.1": ["homeported"], "17.9 22.5 11.6": ["vaporizing"], "-4.6 3.7 6.1": ["striatum"], "-8.7 3.3 13.1": ["marihuana"], "3.1 10.0 7.3": ["sniffle"], "1.1 11.9 9.3": ["bandaging"], "2.0 33.0 6.5": ["irregulars"], "24.2 18.7 28.2": ["buzzard"], "-11.1 -4.4 2.6": ["revalidation"], "3.2 6.0 40.7": ["bouillabaisse"], "3.7 -2.2 -0.7": ["pharmacologist"], "2.8 2.3 5.1": ["rearrangements"], "3.0 2.4 4.4": ["woofers"], "11.3 13.6 5.8": ["squirrelly"], "1.4 16.1 -1.4": ["misinforming"], "-1.9 -1.8 5.2": ["rectors"], "0.0 10.8 3.3": ["alltime"], "-0.9 4.9 8.7": ["sunitinib"], "6.8 9.4 6.1": ["retargeting"], "13.8 10.1 13.4": ["mashes"], "-1.4 1.1 2.5": ["clarinets"], "14.5 12.7 13.1": ["sexless"], "-12.0 4.2 -1.1": ["immunologic"], "1.4 9.2 17.7": ["kabuki"], "9.2 11.7 3.1": ["banishes"], "3.9 3.2 8.3": ["niggly"], "6.9 19.3 18.3": ["calloused"], "-11.9 17.9 22.4": ["bowhunters"], "1.9 8.3 26.9": ["kabobs"], "4.5 11.2 1.2": ["overestimates"], "18.6 18.9 14.1": ["haystacks"], "20.5 -1.8 5.2": ["tottered"], "3.9 9.9 18.2": ["sledders"], "-0.6 11.0 -2.9": ["mischaracterizing"], "2.5 -0.8 13.5": ["fortysomething"], "13.5 6.8 13.6": ["sophisticates"], "8.1 3.0 17.2": ["gibbons"], "6.5 13.7 14.6": ["crashers"], "13.8 -1.0 3.2": ["misc"], "-5.8 4.6 2.8": ["glutathione"], "15.4 4.5 18.5": ["prettily"], "-3.8 16.8 7.0": ["communitarian"], "2.7 3.2 9.3": ["locksmiths"], "2.0 -1.1 7.3": ["livens"], "3.8 3.1 9.5": ["bohemians"], "3.1 21.6 11.1": ["treeline"], "-0.1 9.4 5.1": ["vividness"], "5.7 14.3 14.4": ["unsporting"], "12.0 29.1 -3.9": ["antichrist"], "8.0 2.4 3.3": ["minored"], "5.6 4.8 0.8": ["mugshots"], "4.3 6.4 0.4": ["distrusts"], "7.8 11.9 4.4": ["fixating"], "-10.4 10.2 9.1": ["prorogued"], "0.3 10.1 2.7": ["implementer"], "-1.3 3.0 2.5": ["oustanding"], "4.6 9.2 13.5": ["declawed"], "2.6 5.6 -0.9": ["digitizer"], "9.6 21.0 4.1": ["civilizing"], "-4.4 7.8 35.0": ["braising"], "15.2 23.4 6.8": ["bridgehead"], "5.6 5.8 4.6": ["steamrollered"], "-1.4 7.3 4.0": ["forecloses"], "1.6 3.6 7.8": ["commensurately"], "14.6 -4.8 4.4": ["wends"], "-3.7 3.9 7.9": ["luminaire"], "10.1 5.6 2.7": ["perforating"], "-0.4 10.5 12.8": ["instep"], "-2.1 6.0 16.4": ["superyachts"], "10.5 3.7 0.6": ["doffing"], "-1.7 17.7 6.3": ["leishmaniasis"], "14.6 3.2 13.4": ["megafight"], "4.6 18.2 9.5": ["itches"], "5.7 9.1 18.7": ["jim"], "11.0 4.9 4.9": ["eyecare"], "6.9 3.7 5.2": ["timesaving"], "-5.2 2.1 13.0": ["thrombin"], "0.3 9.9 11.4": ["disinclination"], "-1.6 25.5 9.6": ["neoconservatism"], "0.9 16.7 -1.9": ["incontestable"], "2.1 7.5 2.0": ["haptics"], "5.6 6.9 13.0": ["luminarias"], "5.9 -7.1 17.1": ["skeins"], "-6.2 2.6 19.2": ["kiteboarding"], "3.3 4.7 7.2": ["fiftieth"], "8.7 6.8 21.5": ["taqueria"], "7.9 11.1 6.7": ["browbeating"], "2.6 8.1 11.0": ["seismometers"], "1.9 8.4 47.6": ["seaweeds"], "11.1 12.5 5.9": ["chaotically"], "6.1 4.4 5.9": ["meanderings"], "3.9 4.4 9.1": ["downslope"], "2.6 20.6 3.6": ["caliph"], "-1.2 11.0 2.5": ["interrogatories"], "6.2 3.5 0.4": ["investee"], "6.7 12.2 13.0": ["worming"], "4.3 3.2 9.2": ["whiney"], "-3.0 12.2 10.6": ["uptrends"], "-11.4 7.5 9.2": ["stopes"], "4.6 -0.8 9.6": ["jangly"], "6.0 11.9 4.1": ["particularities"], "-2.4 11.0 8.0": ["numerator"], "5.7 20.3 30.2": ["midge"], "-0.3 7.2 5.7": ["unduplicated"], "4.7 -0.1 12.7": ["cabinetmaker"], "-1.2 -4.4 5.4": ["disbursal"], "18.2 4.1 6.7": ["sombreros"], "-5.3 6.9 3.4": ["hepatology"], "4.8 2.7 8.4": ["unscreened"], "16.6 1.0 8.1": ["clacking"], "5.2 -0.1 11.7": ["halcyon"], "-10.2 22.0 4.3": ["demoralization"], "11.2 8.2 37.9": ["puffins"], "-10.3 9.1 7.8": ["soliloquies"], "-3.9 1.5 -0.7": ["nebulizer"], "11.9 9.0 2.3": ["earsplitting"], "-4.6 6.0 14.0": ["baseboard"], "12.8 -1.7 7.2": ["patchouli"], "-8.6 -2.9 6.7": ["camisole"], "2.4 8.9 5.6": ["muddles"], "4.2 17.3 8.0": ["rowdies"], "12.8 8.0 4.9": ["gaped", "catalyzer"], "3.5 3.9 -2.6": ["barnstormed"], "7.5 1.5 28.9": ["lychee"], "7.5 17.8 0.5": ["sadists"], "10.7 0.1 -4.8": ["rebadged"], "-3.1 19.0 8.2": ["flashfloods"], "5.1 6.7 2.7": ["burgling"], "8.0 15.4 17.2": ["quills"], "4.0 -3.7 7.2": ["toh"], "7.5 -5.4 18.8": ["raffia"], "6.4 7.1 0.9": ["unmemorable"], "2.3 10.6 3.4": ["outranks"], "-0.2 2.8 7.3": ["silversmith", "mhz"], "6.9 -0.3 16.8": ["ceilidh"], "11.1 4.5 12.1": ["snit"], "11.4 7.3 9.1": ["sunburnt"], "2.2 15.0 5.3": ["overcompensating"], "16.9 15.4 11.6": ["nuzzling"], "-4.3 3.4 6.7": ["ulceration"], "4.0 6.5 8.3": ["unschooled"], "12.9 9.7 14.4": ["peal"], "15.4 0.8 1.0": ["timebomb"], "3.1 2.2 34.9": ["fettuccine"], "3.2 6.3 -0.6": ["cutdown"], "-4.5 8.7 6.3": ["equitation"], "-1.6 34.9 8.0": ["fragging"], "5.7 5.8 6.1": ["jamborees"], "-2.7 -0.4 7.4": ["butadiene"], "-4.1 14.0 4.2": ["immunotherapies"], "5.6 2.6 -0.3": ["rorting"], "7.8 1.6 13.2": ["thirtysomethings"], "7.1 5.3 10.0": ["shearer"], "4.3 7.8 7.7": ["midline", "diverticular"], "20.6 9.8 14.3": ["burps"], "-4.7 9.7 4.8": ["documentarians"], "16.3 4.8 7.0": ["vend"], "-1.6 10.9 -0.1": ["adn"], "3.0 7.2 6.3": ["rx"], "10.5 19.7 11.4": ["rustlers"], "10.0 3.2 6.6": ["grandpas"], "-10.8 2.6 11.1": ["neuroticism"], "5.7 2.8 30.1": ["poi"], "7.2 11.8 -0.1": ["lonelier"], "0.1 -0.4 22.8": ["tench"], "4.1 1.6 0.4": ["bootable"], "21.7 3.6 18.9": ["wiggly"], "-4.1 10.8 14.9": ["reseed"], "2.5 -1.4 6.3": ["glycerine"], "-4.2 4.1 1.0": ["laude"], "4.3 -1.3 12.6": ["banqueting"], "5.0 6.7 4.3": ["stil"], "16.8 23.6 13.2": ["atavistic"], "-1.6 11.8 8.4": ["improver"], "1.6 1.8 5.0": ["detouring"], "-4.0 15.2 1.2": ["sanctification"], "-6.1 -0.9 1.7": ["conferment"], "4.8 2.0 1.3": ["titillated"], "-3.4 9.2 8.6": ["labelmates"], "1.0 10.7 6.8": ["consecrating"], "8.9 6.3 6.3": ["heartthrobs"], "-6.8 4.5 10.4": ["memoirist"], "11.3 8.3 8.5": ["daemon"], "8.6 12.4 17.0": ["gamekeeper"], "1.1 0.1 10.9": ["bagasse"], "-7.2 12.4 10.4": ["deadbolt"], "-6.2 4.8 7.1": ["collectability"], "4.8 6.1 12.3": ["unfixed"], "12.0 12.0 4.9": ["multipronged"], "6.1 5.5 10.5": ["filial"], "6.7 14.3 8.3": ["fantasizes"], "14.8 10.4 6.8": ["oooh"], "3.8 7.3 5.3": ["unsettles"], "10.8 -6.4 7.4": ["skimped"], "11.8 8.7 11.3": ["cinder"], "1.1 12.7 3.4": ["humblest"], "0.1 -3.5 0.4": ["reinvestigate"], "13.1 -1.3 8.3": ["paris"], "16.1 2.9 11.7": ["wranglers"], "-1.0 12.7 2.4": ["editorialist"], "-4.8 9.9 9.5": ["gimmes"], "-0.2 17.4 4.0": ["impolitic"], "14.8 7.1 8.3": ["dopes"], "-2.2 -6.2 11.2": ["perc"], "2.9 14.0 5.1": ["neccessary"], "4.0 18.2 22.1": ["roosts"], "-3.8 2.1 0.6": ["retroactivity"], "-2.1 7.5 8.4": ["hankies"], "11.2 7.7 5.4": ["sideswiping"], "7.1 11.3 14.2": ["cultivator"], "-0.1 13.7 7.1": ["clubmates"], "-4.9 16.6 7.1": ["extramarital"], "-1.1 13.0 0.5": ["hereon"], "-0.9 5.6 5.3": ["amlodipine"], "8.3 23.8 7.4": ["outwitting"], "-3.6 3.5 4.0": ["mbpd"], "11.8 5.8 -1.2": ["suprising"], "5.0 4.0 1.3": ["spintronics"], "-0.7 10.4 7.4": ["psychobabble"], "6.4 0.2 2.1": ["biotechnologies"], "5.6 3.4 12.9": ["countrified"], "4.9 2.7 15.1": ["decanter"], "10.5 4.2 5.6": ["poorhouse"], "0.8 2.0 3.6": ["hemorrhagic"], "0.6 3.6 1.3": ["childminder"], "5.7 5.0 18.0": ["dotty"], "4.6 17.0 7.6": ["halitosis"], "-8.1 1.8 2.7": ["letrozole"], "8.2 7.9 11.8": ["shoegaze"], "-5.1 4.7 4.0": ["haemophilia"], "4.0 9.6 9.3": ["cultism"], "2.3 6.3 12.6": ["threshing"], "4.8 6.1 21.5": ["puller"], "-2.9 3.7 2.9": ["adenomas"], "-2.1 6.0 10.2": ["bicarbonate"], "7.6 6.0 10.0": ["tuff"], "11.5 8.9 28.0": ["parfait"], "8.8 6.2 10.0": ["turbos"], "-1.7 4.9 -0.1": ["timelier"], "2.6 -4.7 16.0": ["carwashes"], "9.6 1.5 23.8": ["pearly"], "3.9 -0.4 1.0": ["greenfields"], "8.9 -6.7 1.2": ["moonlighted"], "1.7 -0.2 2.2": ["perfomance"], "-3.1 1.1 9.5": ["nonaccrual"], "-6.0 19.0 4.6": ["wrongness"], "-7.1 4.3 7.2": ["sterilizations"], "7.6 6.7 3.6": ["bawl"], "4.1 7.6 4.5": ["unformed"], "-11.9 2.8 22.0": ["calve"], "11.4 7.7 4.6": ["bellyaching"], "9.3 7.7 18.2": ["unturned"], "6.8 11.6 6.0": ["outruns"], "-6.3 10.1 6.1": ["chiefdom"], "-2.2 35.4 -1.7": ["terroristic"], "3.2 13.2 7.6": ["counterbalancing"], "2.2 5.2 0.4": ["memoriam"], "10.4 16.0 5.5": ["gravitation"], "-2.9 -5.7 9.2": ["nonprofessional"], "0.3 16.2 1.6": ["internationalists"], "6.0 12.5 5.5": ["unbelieveable"], "3.3 6.6 20.8": ["amaryllis"], "7.3 9.7 -0.3": ["reenergize"], "2.2 7.5 4.1": ["scorelines"], "6.0 4.4 28.4": ["weirs"], "11.8 18.5 6.1": ["ineptly"], "-0.1 7.9 9.9": ["injudicious"], "18.5 12.7 23.5": ["puss"], "9.3 8.5 31.3": ["antlered"], "13.2 19.9 10.6": ["sorcerers"], "6.8 -1.4 5.3": ["rebidding"], "-1.3 1.2 -1.4": ["choses"], "30.6 8.4 14.8": ["swirly"], "0.6 8.6 3.4": ["unimpaired"], "10.7 10.6 4.5": ["interwebs"], "12.1 8.2 1.8": ["unmistakeable"], "8.7 -7.9 4.0": ["spiffed"], "7.2 21.0 10.5": ["unalterable"], "6.4 24.6 6.2": ["theocrats"], "5.5 6.1 -4.6": ["demoing"], "-2.3 11.9 5.8": ["combativeness"], "-3.9 -2.6 12.3": ["smallholding"], "-5.2 1.4 14.1": ["cohost"], "13.1 25.3 16.0": ["waggle"], "6.5 21.9 5.6": ["unerringly"], "-3.4 0.9 1.1": ["idiopathic"], "0.6 18.7 9.3": ["unburned"], "7.4 7.2 0.6": ["thay"], "-4.6 10.0 13.0": ["backfilling"], "5.0 3.3 25.4": ["honeydew"], "27.4 20.6 12.9": ["gargoyle"], "-1.1 6.3 1.3": ["congruence"], "3.0 9.7 12.7": ["pleaser"], "5.2 7.7 19.8": ["broads"], "6.5 13.4 13.0": ["festers"], "6.5 18.4 15.7": ["scrappers"], "12.7 3.5 16.9": ["protrusion"], "1.2 13.2 5.9": ["mensch"], "4.7 12.3 2.4": ["disproven"], "-3.2 10.9 17.8": ["tetracycline"], "7.0 3.9 11.1": ["trill"], "11.0 2.5 -6.6": ["headhunted"], "-0.3 16.1 8.5": ["shutterbug"], "6.7 9.6 8.5": ["supernovas"], "-2.9 26.9 13.1": ["sinfulness"], "-0.6 7.2 11.6": ["subpopulations"], "-10.0 6.2 4.8": ["minyan"], "7.7 4.8 16.2": ["tak"], "2.2 14.3 7.8": ["northwesterly"], "1.6 4.1 7.6": ["extrapolations"], "5.2 3.5 5.9": ["handbasket"], "7.5 0.7 -0.7": ["foyers"], "-2.5 10.3 8.5": ["swales"], "8.2 9.1 5.8": ["rediculous"], "10.0 12.0 4.5": ["clearings"], "9.6 -0.6 7.7": ["tidier"], "-2.4 9.1 5.6": ["cutline"], "18.3 8.1 13.4": ["puma"], "6.9 4.8 8.7": ["madison"], "10.2 10.4 27.9": ["bruin"], "-2.8 9.7 3.9": ["adsorption"], "9.0 9.5 18.2": ["wha"], "-7.4 -4.1 18.7": ["butterfat"], "1.3 9.9 3.4": ["graduands"], "6.9 3.3 5.4": ["tidily"], "0.6 4.7 10.2": ["distros"], "-1.7 -10.7 5.1": ["bioanalytical"], "0.6 9.8 3.1": ["harrassed"], "23.0 13.0 20.7": ["phallus"], "3.4 -3.3 7.9": ["isa"], "4.9 -2.0 6.3": ["cor"], "16.8 13.0 1.3": ["rids"], "18.3 5.7 14.2": ["meerkat"], "19.3 16.7 13.7": ["scurries"], "12.5 1.9 4.7": ["multistage"], "13.9 20.9 16.4": ["dodger"], "-7.1 7.2 9.2": ["incarcerations"], "4.3 11.4 10.3": ["superfoods"], "24.1 15.4 25.3": ["buccaneer"], "1.5 9.2 19.2": ["ying"], "-1.7 0.3 1.0": ["longlist"], "6.4 -2.3 13.2": ["silkscreen"], "-0.2 1.0 2.9": ["challans"], "4.7 -0.8 0.0": ["orginal"], "17.0 1.0 6.6": ["unroll"], "-2.9 4.6 12.2": ["electroplating"], "-5.3 5.3 8.1": ["coloratura"], "-0.8 18.7 5.1": ["overextend"], "8.6 11.0 7.6": ["barf"], "1.2 9.8 13.6": ["exurban"], "3.9 3.4 11.5": ["overdeveloped"], "-7.2 10.0 17.4": ["communicant"], "-4.4 5.0 10.5": ["albinism"], "6.3 6.0 5.1": ["mutes"], "-12.8 2.6 6.0": ["clozapine"], "15.9 2.9 1.1": ["cavorted"], "12.9 12.0 10.0": ["tromping"], "16.8 3.4 13.5": ["billowy"], "3.8 7.4 10.7": ["folktales"], "9.4 7.3 8.3": ["demurely"], "-0.1 4.6 4.5": ["equalities"], "8.8 -6.9 12.3": ["cowhide"], "3.8 17.0 -0.8": ["personel"], "4.1 11.4 1.9": ["allround"], "-0.2 12.8 12.7": ["cohabit"], "2.0 15.7 30.8": ["topwater"], "9.0 16.2 8.7": ["parapets"], "7.3 10.1 12.6": ["poplars"], "-0.6 3.7 8.7": ["mbd"], "2.0 20.8 8.4": ["marginals"], "9.0 6.9 21.6": ["scarfed"], "9.9 13.2 7.6": ["mesmeric"], "19.4 0.5 6.8": ["puked"], "-4.7 -1.1 0.2": ["biocompatibility"], "-11.2 -3.8 15.9": ["weanling"], "8.4 1.2 20.1": ["minty"], "-8.5 13.4 9.3": ["taxane"], "2.2 0.7 7.7": ["libidinous"], "13.4 10.3 7.2": ["exhales"], "12.2 15.7 20.5": ["peepers"], "2.3 0.8 30.4": ["papayas"], "-6.0 2.8 4.0": ["telefilm"], "-2.4 15.5 -1.5": ["aider"], "0.9 6.2 8.6": ["superspeedways"], "15.5 18.8 25.4": ["weenie"], "10.6 9.2 21.7": ["macaca"], "-4.9 5.7 5.8": ["barbiturate"], "27.3 13.5 4.0": ["slinger"], "1.5 7.1 20.0": ["groundnuts"], "15.1 10.9 9.3": ["whither"], "4.7 11.7 16.0": ["metalheads"], "4.8 6.8 4.7": ["anachronisms"], "1.7 19.5 -0.3": ["overextending"], "0.2 8.4 11.8": ["yielders"], "7.4 12.0 3.6": ["gestural"], "13.0 4.8 4.5": ["geophysicists"], "-0.2 1.1 2.2": ["butanol"], "9.0 11.2 11.5": ["circumnavigating"], "-7.0 -0.4 13.2": ["kurta"], "7.7 6.4 5.8": ["typists"], "13.1 15.2 10.2": ["nitwit"], "-6.3 12.1 5.0": ["seperated"], "-1.6 8.8 4.3": ["drafter"], "7.3 8.0 10.4": ["leafs"], "-3.0 -0.2 12.7": ["embroideries"], "-1.1 8.4 7.4": ["unlikelihood"], "7.4 7.5 21.2": ["composter"], "16.5 0.7 7.2": ["fusty"], "0.4 10.8 26.1": ["mimosas"], "6.4 4.1 10.0": ["swingin"], "10.0 2.6 8.5": ["sopping"], "3.8 8.2 6.8": ["meritocratic"], "-2.8 4.2 0.7": ["perfumery"], "4.1 29.8 20.9": ["gunboat"], "3.1 8.0 6.5": ["olden"], "20.1 -1.4 8.1": ["cheapo"], "-5.8 12.2 9.9": ["crawlspace"], "-1.4 27.8 10.5": ["replayability"], "-5.1 13.8 8.1": ["rallyists"], "-7.9 -0.1 4.5": ["decongestants"], "5.9 1.7 5.6": ["mechatronics"], "6.9 16.3 7.9": ["maricon"], "-3.1 14.5 28.4": ["overwinter"], "8.3 6.7 8.7": ["airgel"], "0.6 2.9 -2.4": ["decamping"], "4.1 8.4 11.6": ["cigs"], "10.5 12.7 6.9": ["youve"], "-5.1 3.7 7.0": ["rehashes"], "5.7 12.2 3.8": ["crystallizing"], "3.3 9.8 20.1": ["multihulls"], "-3.4 11.8 4.5": ["interreligious"], "2.1 21.4 12.6": ["bloodying"], "-2.8 8.5 1.2": ["disinterred"], "-14.1 -4.0 4.0": ["attendence"], "-3.7 0.7 0.2": ["appt"], "13.9 6.2 6.3": ["lucre"], "4.7 0.4 16.1": ["horsey"], "0.4 16.8 7.3": ["haymakers"], "-9.9 4.5 0.6": ["understudied"], "-1.4 23.0 2.1": ["multilaterally"], "8.6 9.9 4.1": ["magnetics"], "4.6 0.1 3.2": ["taurine", "meltblown"], "5.9 17.0 8.1": ["obfuscating"], "3.0 -1.2 12.7": ["keratin"], "4.4 7.0 7.8": ["necrophilia"], "18.0 13.6 18.8": ["flippin"], "2.5 5.5 3.0": ["tragicomedy"], "-1.3 9.3 11.0": ["oxidize"], "13.4 6.3 12.2": ["overfed"], "-2.6 7.6 -0.7": ["wiling"], "4.6 3.5 3.3": ["concentrators"], "5.2 16.0 0.8": ["witchhunt"], "11.5 16.5 4.9": ["megalomaniacal"], "12.2 -3.0 9.2": ["boomlet"], "11.2 9.6 12.9": ["murkiness"], "-8.3 3.0 8.0": ["syariah"], "12.6 9.2 1.6": ["governement"], "2.7 0.2 3.7": ["ob"], "0.2 -5.9 -2.8": ["freelanced"], "-7.1 1.4 2.8": ["multiprocessor"], "1.0 -3.0 -2.4": ["regularizing"], "2.2 8.8 3.0": ["ungrounded"], "10.1 0.0 -0.6": ["discontinues"], "7.6 13.1 10.0": ["sickeningly"], "2.5 1.7 4.4": ["embroider"], "2.3 13.1 -4.7": ["disowning"], "-4.2 7.6 2.6": ["powersports"], "7.6 17.2 16.0": ["moonsault"], "6.4 18.2 8.5": ["emasculate"], "-6.2 8.6 25.2": ["allspice"], "7.9 25.3 11.4": ["runes"], "1.6 -5.2 14.3": ["hookahs"], "-0.1 7.5 15.9": ["airboats"], "-8.2 5.0 8.7": ["ordaining"], "-9.1 -3.5 7.6": ["officiates"], "1.1 0.5 0.2": ["ghostwriting"], "-3.5 5.1 12.5": ["pistes"], "-5.2 1.0 2.7": ["dysplasia"], "13.7 4.7 12.6": ["cloverleaf"], "2.1 13.3 19.9": ["baste"], "-9.6 6.3 1.4": ["embolization"], "4.2 4.6 35.7": ["carpaccio"], "21.3 15.3 4.8": ["goddamned"], "-11.0 5.5 2.8": ["callups"], "9.6 6.1 0.7": ["mends"], "5.7 9.1 2.9": ["astounds"], "6.8 6.4 7.9": ["rooters"], "8.3 5.3 12.3": ["trophyless"], "3.7 3.3 10.5": ["tats"], "6.9 3.8 14.5": ["clumped"], "4.3 1.9 10.8": ["disproportionally"], "22.3 14.3 15.5": ["wham"], "-3.3 8.8 20.5": ["boaties"], "-4.6 14.6 13.1": ["melanocytes"], "-9.1 15.2 6.0": ["intermarried"], "27.5 -4.2 5.5": ["latticework"], "-2.5 15.5 23.8": ["taxonomic"], "1.7 7.4 4.4": ["imitative"], "12.5 13.2 13.1": ["graceless"], "2.7 12.5 9.2": ["dunker"], "4.0 17.7 6.8": ["warder"], "10.4 11.0 20.3": ["lariat"], "25.6 2.9 18.1": ["multicolor"], "6.5 3.4 0.4": ["revitalizes"], "2.3 8.2 6.7": ["sherpas"], "6.8 2.9 15.3": ["persnickety"], "-4.8 27.4 6.2": ["lashkars"], "3.3 12.4 12.6": ["recessive"], "6.7 5.2 22.1": ["strudel"], "0.5 0.6 2.6": ["gipsy"], "16.1 12.1 7.4": ["sidle"], "15.4 15.5 5.5": ["unnervingly"], "3.4 7.0 8.9": ["catfights"], "2.0 -2.7 10.8": ["biomanufacturing"], "1.0 1.5 4.9": ["mappings"], "14.3 31.7 9.5": ["avenger"], "10.5 9.9 1.6": ["stumper"], "-1.2 15.0 5.1": ["schematically"], "7.3 5.1 11.2": ["beanies"], "12.6 -7.7 -4.3": ["annouced"], "2.7 19.0 6.0": ["hotheads"], "-0.1 5.0 -1.9": ["demur"], "-8.8 -1.4 8.4": ["remastering"], "-0.9 15.3 11.6": ["reenactors"], "3.6 18.9 15.7": ["kingship"], "-4.9 5.6 1.5": ["tesamorelin"], "-3.7 15.6 9.8": ["redzone"], "-5.3 5.5 13.5": ["sightsee"], "13.1 19.9 15.8": ["doth"], "-6.8 1.5 0.8": ["transcode"], "4.7 14.9 2.5": ["preempting"], "-10.8 -1.7 7.0": ["childminders"], "-2.0 12.4 5.4": ["cameraphone"], "14.2 12.8 4.4": ["realigns"], "7.1 1.1 11.8": ["aah"], "4.4 -6.7 6.6": ["dovetailing"], "1.3 2.6 23.7": ["brinjal"], "-2.8 -1.5 6.8": ["emceeing"], "9.5 4.6 7.8": ["oldsters"], "-0.4 11.1 -1.0": ["diffuses"], "0.4 8.3 5.9": ["overtaxing"], "8.9 11.6 10.0": ["fellatio"], "19.4 4.1 12.0": ["glitchy"], "5.6 6.4 1.8": ["connective"], "14.9 2.9 13.7": ["tchotchkes"], "1.1 11.7 13.8": ["looper"], "-4.1 5.4 1.2": ["approachability"], "-1.0 9.4 5.6": ["amine"], "-0.8 5.1 12.9": ["homestate"], "-6.1 -1.6 6.7": ["curates"], "0.4 6.4 6.2": ["sticklers"], "16.1 32.3 -2.5": ["victoriously"], "9.0 20.3 6.8": ["smashmouth"], "-3.3 25.0 8.7": ["peacenik"], "9.7 13.5 5.4": ["straggling"], "2.0 11.2 5.8": ["specialness"], "7.5 16.8 7.4": ["dimensionally"], "0.7 9.3 -2.2": ["repenting"], "-3.4 8.1 7.7": ["shadings"], "-2.4 3.0 15.3": ["newbuild"], "12.0 -3.1 9.3": ["adv"], "1.2 -3.6 16.7": ["waistcoats"], "7.3 2.2 3.5": ["ov"], "2.8 27.4 4.7": ["appeasers"], "7.9 11.7 17.3": ["chortle"], "8.5 6.6 12.8": ["superbowl"], "-0.6 1.4 6.6": ["farces"], "1.7 4.1 10.0": ["caspase"], "-10.0 0.3 2.1": ["breathalyzed"], "-4.1 3.4 11.5": ["calligrapher"], "17.4 -2.8 0.8": ["spruiking"], "6.5 16.7 7.8": ["baseliner"], "-12.0 -1.2 0.4": ["workovers"], "10.6 16.1 10.0": ["reddening"], "2.3 24.8 6.0": ["knowable"], "16.8 7.7 10.8": ["spangled"], "13.5 7.8 7.7": ["brandishes"], "3.2 6.1 10.9": ["calligraphic"], "21.2 8.2 28.7": ["popsicle"], "-10.6 7.6 0.4": ["relinquishment"], "10.8 -8.0 16.5": ["gingham"], "17.3 16.4 20.1": ["rattler"], "2.2 13.7 5.6": ["asymmetries"], "11.8 6.7 6.5": ["leeching"], "9.8 14.4 4.4": ["clanger"], "11.4 14.2 13.0": ["squeamishness"], "1.0 4.4 7.4": ["presbyopia"], "16.3 4.0 11.8": ["yodel"], "1.8 8.9 0.9": ["pertinently"], "-3.6 1.1 13.0": ["boro"], "-1.4 10.0 12.5": ["leaguewide"], "-0.1 6.3 14.4": ["tik"], "17.2 3.8 15.6": ["extrusions"], "7.3 1.4 6.5": ["gestating"], "-9.3 10.1 8.4": ["reorders"], "9.8 4.9 -4.4": ["snooped"], "7.1 14.5 4.5": ["ite"], "-10.6 1.2 3.3": ["isotretinoin"], "16.6 3.0 35.3": ["sweetcorn"], "-8.7 15.6 18.5": ["batterer"], "19.1 1.4 14.2": ["decadelong"], "-0.3 1.0 12.2": ["namin"], "4.2 2.3 5.6": ["reseal"], "-3.7 4.3 5.0": ["interjections"], "-0.1 16.7 15.3": ["heli"], "1.1 7.1 15.3": ["taek"], "6.6 5.3 13.6": ["rococo", "fauvist"], "-2.6 12.7 12.8": ["heartedness"], "-7.6 -3.8 3.5": ["clerkship"], "14.9 10.2 5.4": ["incantations"], "2.7 28.8 -1.4": ["jehadi"], "22.0 4.6 3.8": ["frenetically"], "8.0 -0.2 5.0": ["curiouser"], "1.8 2.8 17.0": ["meltwater"], "1.3 13.6 27.3": ["hosta"], "-4.9 -0.1 7.5": ["fenofibrate"], "26.4 7.3 3.9": ["highflying"], "-4.6 2.6 9.0": ["tonally"], "0.8 8.4 11.0": ["silicified"], "1.5 4.4 3.0": ["hydrogenation"], "1.8 14.3 7.6": ["shallowest"], "2.1 -0.4 14.8": ["aerators"], "-1.5 2.5 -1.3": ["reexamining"], "-6.2 13.3 5.5": ["dunams"], "1.0 7.5 16.4": ["sulfides"], "6.1 4.3 3.4": ["superhit"], "0.9 -2.6 10.6": ["corsages"], "5.5 -0.7 -0.1": ["recyclability"], "0.3 15.3 16.0": ["impudence"], "-1.5 1.0 5.7": ["superintendant"], "-3.0 -2.3 8.1": ["retentions"], "12.5 9.1 9.1": ["coffeemaker"], "8.7 6.2 14.1": ["meatpacker"], "-8.3 5.1 3.8": ["abstains"], "6.9 8.3 12.0": ["gt"], "12.5 -2.9 6.4": ["keychains"], "7.2 6.4 1.9": ["tramped"], "14.4 0.1 9.7": ["skee"], "-9.2 -7.3 2.3": ["workweeks"], "6.1 1.7 8.1": ["kwaito"], "8.6 0.8 11.3": ["compactors"], "8.6 8.7 11.7": ["twaddle"], "-6.2 0.1 12.2": ["paroles"], "8.8 6.1 8.8": ["carparks"], "1.1 15.5 -3.9": ["falsifications"], "-2.2 9.3 7.4": ["acculturation"], "4.4 6.5 4.3": ["liveblog"], "3.6 4.6 3.5": ["outputting"], "1.0 0.0 -1.5": ["propositioning"], "12.3 3.3 8.3": ["woodshop"], "10.6 15.9 8.1": ["enigmas"], "-0.8 2.0 2.2": ["collaterals"], "6.1 12.9 5.5": ["expedience"], "5.1 5.4 10.9": ["industrializing"], "-2.6 5.8 -1.5": ["articulately"], "6.1 -1.6 7.5": ["dallied"], "-1.7 10.8 19.9": ["brushwork"], "17.1 6.0 -2.2": ["gramophone"], "1.6 3.5 11.8": ["fishtail"], "3.4 6.8 5.4": ["drumline"], "5.0 10.6 10.5": ["brownout"], "3.9 10.3 10.7": ["unpolluted"], "-7.4 6.9 16.5": ["mintage"], "10.7 8.4 23.8": ["macaw"], "-3.2 8.3 6.8": ["sportsmanlike"], "-7.3 11.2 8.3": ["expository"], "-2.6 10.5 2.2": ["opp"], "4.1 -4.8 -7.0": ["syndicator"], "10.4 13.6 5.1": ["cleaving"], "4.4 -1.1 23.1": ["cheesemaker"], "-6.8 1.8 3.7": ["struckout"], "2.9 4.6 6.8": ["extracellular"], "10.2 9.1 11.9": ["morn"], "1.9 17.6 3.0": ["postured"], "2.4 -4.5 14.9": ["prizegiving"], "-0.5 9.7 3.2": ["comming"], "10.8 10.6 9.5": ["russian", "splay"], "5.6 9.8 7.8": ["ventriloquism"], "3.2 12.3 14.1": ["decimals"], "1.8 21.5 7.1": ["militarize"], "-4.1 -0.6 10.4": ["pmt"], "7.4 3.4 13.6": ["kan"], "3.6 11.9 1.6": ["unmade"], "5.9 7.6 10.6": ["cloister"], "7.1 3.9 8.6": ["binmen"], "7.9 22.4 8.7": ["plasmids"], "-0.2 1.7 2.4": ["overcompensated"], "26.5 7.7 14.4": ["teensy"], "-6.8 10.7 4.5": ["offroad"], "11.9 18.0 12.2": ["formless"], "8.7 -6.1 6.3": ["scrimped"], "16.6 3.0 4.8": ["quirkiest"], "0.0 5.3 12.1": ["elastin"], "19.2 12.5 18.7": ["sphinx"], "11.5 6.4 8.9": ["neem"], "1.6 10.8 0.1": ["millibars"], "-3.8 21.7 7.6": ["hudna"], "1.3 -0.3 19.1": ["beachy"], "16.4 12.1 15.8": ["cubist"], "4.8 17.3 6.0": ["relativistic"], "12.1 4.1 7.7": ["jalopy"], "0.9 -1.4 7.7": ["subtitling"], "4.0 9.5 2.7": ["gaol"], "0.2 10.1 17.5": ["judoka"], "5.4 7.2 6.6": ["ick"], "3.5 17.0 18.8": ["promontory"], "1.5 26.0 11.5": ["gamepad"], "-1.7 4.3 -1.5": ["manifestoes"], "2.8 17.8 3.7": ["inarguable"], "10.1 5.1 17.9": ["sook"], "4.4 10.9 11.1": ["uncommunicative"], "-5.5 8.3 5.1": ["nullah"], "6.3 9.0 14.6": ["grubbing"], "-1.6 4.8 13.8": ["qat"], "4.8 1.5 5.3": ["leasable"], "-2.9 10.3 12.7": ["tubewells"], "14.3 -0.6 3.7": ["pushchairs"], "3.9 7.4 0.7": ["ontology", "thedecision"], "6.7 -0.6 12.5": ["knockabout"], "13.1 9.9 16.7": ["squawks"], "10.6 3.2 7.5": ["intial"], "-4.4 -7.4 6.8": ["retests"], "-5.6 3.6 9.8": ["folklorist"], "5.2 3.5 -0.7": ["superceded"], "10.6 3.6 4.2": ["buisness"], "-5.9 4.6 -5.0": ["neonatology"], "10.8 5.9 9.4": ["spectrograph"], "6.1 7.3 9.4": ["diagramming"], "-6.5 11.2 -0.6": ["arraign"], "9.5 11.2 28.5": ["tong"], "-4.4 2.9 21.4": ["dairymen"], "8.0 -3.9 14.7": ["sequinned"], "12.9 11.6 6.1": ["updater"], "6.2 9.1 8.2": ["vale"], "-3.2 7.8 11.4": ["angiogenic"], "0.8 11.3 7.9": ["meditates"], "-1.3 36.2 10.6": ["infiltrator"], "2.1 17.4 4.8": ["sardonically"], "3.8 7.0 32.2": ["persimmons"], "-4.4 10.3 -0.9": ["iterate"], "-4.2 8.3 8.1": ["suturing"], "11.6 6.3 19.4": ["hoo"], "-2.7 -6.5 8.6": ["preregistered"], "-0.8 2.8 7.6": ["simpatico"], "10.9 12.0 -2.0": ["enviroment"], "1.9 7.1 11.9": ["orthodoxies"], "5.5 1.1 15.3": ["androstenedione"], "8.3 16.4 15.8": ["divination"], "1.2 18.8 -5.8": ["bombmaker"], "0.8 7.1 0.6": ["treaded"], "21.0 4.2 21.4": ["bing"], "8.0 10.9 25.2": ["trawls"], "-2.2 -4.0 10.7": ["regencies"], "5.0 9.2 11.1": ["mystifies"], "-6.6 8.2 11.1": ["evasiveness"], "17.0 14.7 23.5": ["blackbird"], "5.4 15.8 15.8": ["snipes"], "6.9 20.7 7.1": ["nightstick"], "4.2 10.7 4.6": ["melees"], "17.3 9.3 15.5": ["scuttles"], "2.4 8.7 -3.8": ["outreaches"], "13.1 5.8 -4.3": ["suprisingly"], "1.2 4.6 11.8": ["lazier"], "-3.1 12.6 13.3": ["riffraff"], "10.1 15.0 15.0": ["fagots"], "-0.9 -5.2 2.3": ["polyamide"], "2.2 22.0 4.9": ["ethnocentric"], "10.1 -1.5 12.2": ["backlights"], "4.4 16.1 4.0": ["separateness"], "6.2 3.0 12.8": ["preprinted"], "-12.2 -1.5 7.4": ["teleseminar"], "10.5 11.8 8.8": ["userbase"], "20.2 13.1 30.1": ["newt"], "6.9 19.6 2.6": ["westerner"], "2.1 8.4 11.2": ["oddness"], "17.8 7.0 -3.1": ["financer"], "14.5 9.3 9.7": ["emoticon"], "6.8 25.9 5.4": ["outfox"], "20.4 6.1 -2.3": ["automotives"], "-0.9 5.7 0.6": ["interlocutory"], "-3.4 4.4 3.9": ["ppd"], "-4.5 -0.4 2.8": ["reflow"], "7.7 13.7 13.3": ["tribespeople"], "-1.5 2.8 22.1": ["keelboat"], "-1.6 -0.1 13.2": ["crossbred"], "13.0 19.8 12.1": ["bloodsucker"], "2.4 2.6 5.8": ["impinged"], "-1.1 0.4 5.0": ["sera"], "4.7 14.3 12.8": ["alkali"], "0.7 14.6 10.6": ["preludes"], "7.7 3.3 6.2": ["takin"], "4.0 10.0 6.5": ["modded"], "8.1 7.6 13.1": ["friar"], "-9.6 4.0 8.4": ["fluoridated"], "8.4 13.3 18.5": ["doggies"], "2.4 10.4 5.2": ["lamentably"], "11.0 12.9 9.9": ["sanctimony"], "16.2 5.6 -2.8": ["digitalized"], "8.2 9.9 13.9": ["roman"], "2.0 26.0 3.1": ["ungoverned"], "5.0 17.5 -0.7": ["abstractly"], "15.6 12.7 14.4": ["toons"], "5.0 14.0 4.5": ["subsume"], "8.3 18.7 0.2": ["piously"], "-9.3 9.8 6.1": ["reshoots"], "-0.4 12.4 -1.5": ["hagiography"], "1.0 1.8 4.0": ["nur"], "-0.4 1.9 8.4": ["kyu"], "2.7 15.0 3.6": ["overground"], "10.3 4.7 8.5": ["fuzzed"], "9.6 9.7 3.2": ["nonfunctional"], "10.8 11.7 7.7": ["gayest"], "8.3 14.2 6.1": ["mismanage"], "14.2 12.7 2.6": ["disasterous"], "0.4 -1.0 6.8": ["bebe"], "11.8 2.2 2.2": ["pvt"], "7.1 14.3 -0.7": ["wile"], "14.7 6.1 11.6": ["velcro"], "-3.2 10.6 27.5": ["mustards"], "12.4 10.1 4.1": ["plods"], "-2.5 8.6 13.4": ["throwaways"], "5.9 11.2 6.9": ["buffoonish"], "24.1 14.2 16.9": ["cherub"], "-1.7 9.0 6.9": ["fuzziness"], "11.9 -3.5 6.7": ["nonagenarian"], "10.2 -1.9 34.9": ["shucked"], "5.8 2.9 10.0": ["wid"], "1.7 13.4 1.1": ["incompletely"], "7.0 1.0 15.3": ["emigres"], "2.4 -0.1 14.9": ["flagstone"], "15.0 29.7 14.9": ["vipers"], "11.2 6.7 6.7": ["quaffing"], "-4.2 19.2 11.4": ["crossers"], "9.4 9.4 10.7": ["overregulation"], "1.9 4.2 9.3": ["andro"], "2.2 11.7 13.5": ["louvers"], "7.6 11.2 18.4": ["softies"], "17.0 5.5 14.3": ["tepee"], "0.7 -0.1 10.1": ["necropsies"], "9.5 23.5 9.0": ["inquisitor"], "4.6 14.1 19.7": ["junipers"], "-4.3 8.5 11.5": ["cryotherapy"], "8.4 14.7 11.2": ["flunkies"], "6.3 0.7 12.1": ["glen"], "2.0 6.1 11.8": ["concreting"], "5.3 2.8 6.4": ["tosh"], "11.3 9.9 13.2": ["smartbook"], "-8.2 11.4 -2.1": ["driveable"], "-5.4 9.9 3.3": ["awakenings"], "12.3 12.6 4.5": ["kickass"], "-2.2 6.4 13.1": ["vagrancy"], "-5.1 0.1 12.1": ["neurogenesis"], "6.0 8.5 15.0": ["trifles"], "-1.2 7.1 10.5": ["rightsizing"], "12.2 12.1 10.9": ["prodigiously"], "6.0 4.0 7.8": ["saddlebags"], "11.8 4.1 4.4": ["browses"], "9.2 18.7 7.4": ["lordship"], "3.7 18.6 16.5": ["courtier"], "-9.6 3.4 2.0": ["headship"], "8.7 9.8 10.7": ["ahhh"], "11.9 9.5 5.6": ["bagman"], "2.5 29.5 6.1": ["rejectionist"], "-4.9 19.5 4.8": ["majoritarian"], "-8.0 -0.8 7.2": ["gur"], "17.5 12.7 7.5": ["poseurs"], "19.9 7.6 5.5": ["megaplex"], "-2.9 5.9 36.2": ["tidelands"], "-9.3 2.8 0.6": ["exhumations"], "-4.0 4.2 0.6": ["glovebox"], "2.4 4.6 3.2": ["refered"], "20.5 20.0 24.8": ["harpoons"], "-0.2 10.0 7.2": ["grandmasters"], "3.8 9.9 3.9": ["sacker"], "-5.3 6.6 2.8": ["blooding"], "8.2 19.0 -3.8": ["extraterritorial"], "3.2 9.1 7.4": ["onballer"], "3.5 0.8 16.5": ["masseurs"], "14.6 -4.1 13.1": ["sleeved"], "-3.0 4.1 13.5": ["chateaux"], "2.9 14.6 52.3": ["amberjack"], "-1.6 11.0 19.2": ["mulches"], "-6.0 13.5 7.1": ["careerist"], "-7.1 6.5 3.3": ["programmatically"], "10.4 10.2 8.1": ["bimbos"], "12.3 6.2 13.2": ["corker"], "6.5 6.2 12.9": ["uninspected"], "10.8 16.1 3.0": ["tinkerer"], "-7.6 5.6 11.1": ["epithelium"], "0.8 5.7 15.8": ["speechifying"], "9.7 9.1 7.9": ["directionally"], "-5.3 5.3 4.6": ["quercetin"], "8.5 -0.7 7.8": ["telethons"], "21.8 9.3 18.8": ["cauldrons"], "-6.6 8.2 2.0": ["hypnotism"], "0.8 24.7 10.5": ["resupplied"], "9.4 8.0 8.3": ["bastardized"], "2.3 8.0 3.7": ["diversities"], "7.9 -7.6 11.1": ["wadded"], "7.8 10.5 4.6": ["confiscates"], "10.9 -2.2 14.1": ["bouffant"], "8.6 23.4 7.7": ["badder"], "-1.3 14.7 46.9": ["pickerel"], "4.1 6.5 16.6": ["frankincense"], "7.0 13.8 10.2": ["interrelationship"], "12.3 4.1 14.5": ["gables"], "-2.5 4.7 15.8": ["unsweetened"], "-2.0 -1.5 4.6": ["remunerations"], "4.5 5.7 4.7": ["aren"], "-13.0 4.0 6.8": ["proteinuria"], "19.2 -4.3 6.6": ["lassoed"], "-3.7 11.4 -0.7": ["creditably"], "-0.6 15.5 3.9": ["trachoma"], "5.8 2.0 5.8": ["collectorate"], "5.1 6.4 6.2": ["boonies"], "3.1 16.2 6.5": ["clairvoyance"], "-2.9 3.5 8.1": ["yi"], "4.7 7.3 5.6": ["coarsening"], "0.3 7.2 6.8": ["sagacious"], "3.3 14.6 3.8": ["discomfiture"], "4.6 5.1 4.8": ["oversea"], "-4.1 -3.8 9.9": ["citrate"], "21.7 5.7 -0.8": ["rebrands"], "11.6 3.0 13.5": ["yoghurts"], "4.9 7.8 0.4": ["reneges"], "4.4 5.7 8.6": ["ings"], "-4.5 19.8 10.3": ["discriminations"], "11.0 16.9 11.4": ["splatters"], "4.4 14.2 7.0": ["detriments"], "7.0 -0.2 4.3": ["indaba"], "-5.5 26.0 -0.0": ["dissention"], "-3.5 8.1 2.0": ["forsee"], "-1.3 0.0 5.3": ["multithreaded"], "11.5 27.3 16.3": ["minigame"], "0.2 15.6 7.6": ["demilitarize"], "16.3 15.2 5.1": ["wedgie"], "2.4 3.7 9.9": ["mts"], "-0.2 9.2 12.3": ["chartists"], "-3.5 3.9 6.9": ["lensed"], "-0.1 6.4 12.1": ["basslines"], "-8.8 1.6 6.3": ["rheumatologists"], "-3.8 6.8 2.0": ["repping"], "11.3 5.4 16.8": ["blahs"], "4.6 10.4 10.8": ["tenuously"], "-1.9 -0.6 12.0": ["acupuncturists"], "-6.8 9.7 -4.0": ["testable"], "3.2 9.6 7.2": ["silicate"], "2.3 5.3 9.1": ["canto"], "-1.0 5.7 15.4": ["mandi"], "-1.6 6.6 3.4": ["selectboard"], "-0.1 7.0 8.0": ["twinges"], "-1.2 5.1 3.5": ["spadework", "esses"], "6.5 8.0 7.3": ["trenchcoat"], "-1.1 15.4 9.8": ["reciprocation"], "3.7 14.7 6.9": ["stoical"], "11.4 11.8 1.2": ["reimagine"], "-9.2 9.6 8.4": ["worldliness"], "10.4 1.5 6.8": ["bungs"], "-3.1 6.3 7.0": ["serous"], "4.0 19.2 7.7": ["attritional"], "7.1 2.1 3.0": ["twittered"], "3.0 9.1 6.0": ["obits"], "-6.1 13.0 6.0": ["automatics"], "-6.1 9.1 4.3": ["retransmit"], "0.6 10.5 7.3": ["smudging"], "10.9 10.7 9.0": ["familiarly"], "5.7 0.2 9.6": ["pandals"], "2.1 -1.3 4.5": ["toners"], "8.1 0.3 21.0": ["cooper"], "4.3 6.2 12.1": ["fretboard"], "-0.7 12.6 2.7": ["soundman"], "19.0 5.6 5.8": ["doodads"], "7.3 14.7 44.5": ["cormorant"], "12.7 6.4 14.3": ["creaming"], "4.5 -3.0 2.5": ["gasifier"], "5.1 5.2 4.1": ["preempts"], "-5.9 10.5 11.8": ["improvises"], "-1.6 1.3 4.2": ["intranasal"], "-0.1 22.6 3.0": ["penetrator"], "-0.9 2.5 20.8": ["silting"], "14.3 8.6 18.8": ["wrack"], "12.4 3.7 4.9": ["yawner"], "9.4 -0.2 20.5": ["coco"], "-1.8 -1.0 0.6": ["gheraoed"], "-0.2 6.2 4.2": ["percentiles"], "7.9 10.9 2.6": ["backrooms"], "10.5 2.1 19.4": ["pullers"], "-1.5 0.2 5.9": ["rowdier"], "11.9 1.2 10.1": ["meowing"], "-6.3 7.3 12.4": ["romcom"], "1.0 1.6 13.0": ["pueblos"], "12.5 15.0 8.6": ["kleptocracy"], "-0.7 7.7 0.2": ["reregister"], "5.2 12.1 11.5": ["hybridized"], "2.2 11.3 8.8": ["mispriced"], "3.2 14.7 6.8": ["unreformed", "burkas", "alveoli"], "3.7 8.2 6.8": ["recumbent"], "11.2 3.4 23.2": ["caramels"], "-7.5 28.3 2.4": ["tradecraft"], "18.2 2.5 13.7": ["beanpole"], "6.0 5.7 16.4": ["cornices"], "13.8 11.6 10.9": ["potentates"], "-7.8 14.6 3.3": ["shortwave"], "-7.1 10.1 11.3": ["inventorying"], "3.6 -3.2 4.2": ["apixaban"], "2.4 5.3 12.0": ["endorphin"], "14.5 10.1 14.5": ["suckle"], "11.6 16.3 2.4": ["perdition"], "26.3 21.4 16.2": ["humanoids"], "11.4 16.0 7.4": ["impassively"], "-8.5 2.5 1.0": ["probated"], "6.5 15.6 2.5": ["emancipate"], "-5.4 1.6 0.0": ["prosumers"], "-2.9 6.7 5.9": ["inattentiveness"], "6.4 -1.6 1.0": ["subleased"], "9.2 11.6 9.4": ["darnedest"], "-12.4 -1.6 2.8": ["mmcfd"], "1.8 1.5 10.0": ["whets"], "10.2 5.7 13.8": ["dave"], "18.7 2.6 -0.3": ["toolmaker"], "-4.5 9.7 18.1": ["cottagers"], "-1.7 10.9 4.1": ["sanitization"], "4.0 4.8 7.4": ["springboards"], "9.9 3.8 12.0": ["ned"], "2.8 12.3 4.5": ["pak", "ied"], "10.4 -0.0 1.2": ["optimizer"], "0.5 9.6 12.1": ["chancy"], "-3.2 5.5 11.9": ["winterize"], "6.8 4.1 16.0": ["drillships"], "1.3 5.6 6.9": ["eruv"], "17.8 15.1 5.5": ["hubristic"], "9.0 11.0 14.3": ["belfry"], "5.5 14.9 12.4": ["unpredicted"], "-0.7 11.8 20.0": ["asters"], "1.9 17.5 12.1": ["purposeless"], "13.4 4.3 6.2": ["duster"], "7.1 3.5 7.6": ["bezels"], "1.4 7.3 7.5": ["opex"], "-1.0 3.7 7.2": ["whiten"], "9.7 0.7 4.6": ["oohing"], "3.0 15.3 11.7": ["cutaways"], "10.0 6.9 30.3": ["diatoms"], "10.6 12.4 9.5": ["inverting"], "8.4 8.8 7.4": ["biathletes"], "3.6 4.0 1.3": ["multivariate"], "3.4 5.7 1.5": ["expropriations"], "-4.4 1.0 13.6": ["abutments"], "5.4 12.1 21.7": ["dhows"], "-1.8 7.4 9.1": ["dishy"], "4.2 12.7 41.6": ["loggerhead"], "-1.9 6.4 1.7": ["sensationalizing"], "2.2 13.0 9.3": ["campesinos"], "-2.1 5.8 8.0": ["fibrinogen"], "-5.9 8.0 -1.0": ["dvds"], "8.9 1.4 10.6": ["reshoot"], "-0.9 1.3 9.1": ["consistory"], "16.1 16.8 11.1": ["bozo"], "0.9 14.2 3.0": ["straightest"], "-2.2 6.6 15.9": ["antes"], "4.6 3.3 18.7": ["matzoh"], "16.7 5.5 46.2": ["urchin"], "-6.3 2.2 27.7": ["ribeye"], "6.3 6.7 15.0": ["gu"], "7.1 11.6 11.7": ["appreciatively"], "-1.1 3.3 12.2": ["ilmenite"], "2.7 6.3 10.2": ["employments"], "-3.8 7.2 8.2": ["annealing"], "9.6 4.9 10.8": ["herder"], "6.8 13.9 10.8": ["roomie"], "7.1 16.9 3.7": ["protean"], "11.3 12.6 5.5": ["jackasses"], "4.9 5.0 12.0": ["orderbook"], "10.9 0.1 6.9": ["micropayment"], "2.8 4.4 7.5": ["stockist"], "12.9 15.6 3.4": ["perfects"], "7.1 13.3 14.1": ["cruder"], "-2.1 8.1 1.7": ["radionuclides"], "9.2 8.4 16.7": ["superfood"], "-12.4 25.6 0.5": ["subjection"], "3.0 2.1 16.6": ["unframed"], "5.1 2.9 15.3": ["manicurists"], "12.6 5.8 16.6": ["globules"], "1.9 10.5 3.9": ["galvanizes"], "-7.6 6.0 2.1": ["colloquy"], "7.1 1.9 13.8": ["petticoats"], "12.4 28.5 4.9": ["perfidious"], "9.2 3.1 20.9": ["basketry"], "5.8 0.6 7.5": ["mor"], "-1.9 3.5 7.4": ["untucked"], "7.3 7.5 9.8": ["xml"], "0.1 -0.4 10.4": ["naman"], "18.6 14.5 7.2": ["dreamscape"], "5.5 11.3 12.4": ["backlot"], "5.8 14.5 2.3": ["vibrational"], "-11.6 3.2 8.7": ["recompletion"], "-7.3 12.3 1.7": ["cognizable"], "11.3 8.8 7.1": ["disinvest"], "-0.3 19.7 13.1": ["riffles"], "10.2 19.0 7.3": ["immobilizing"], "9.9 1.2 8.4": ["yoked"], "1.3 12.9 11.5": ["fianc"], "11.2 1.6 24.7": ["plateful"], "14.5 10.2 1.8": ["cozied"], "1.2 7.1 3.5": ["threshhold"], "-7.9 8.2 8.5": ["enactments"], "0.8 -1.6 -1.2": ["multisite"], "1.6 9.5 14.6": ["flubbing"], "-1.2 11.7 9.6": ["groomsman"], "10.0 15.5 24.7": ["goldenrod"], "3.4 10.3 11.7": ["retroviruses"], "0.1 0.4 0.7": ["collegium"], "-3.6 7.9 30.0": ["jaggery"], "2.3 4.0 1.5": ["luxuriate"], "10.7 4.8 5.3": ["switchback"], "-0.1 5.8 7.2": ["sid"], "22.5 25.0 10.3": ["cyborgs"], "-5.9 14.8 9.0": ["overwriting"], "10.4 6.4 10.7": ["earthmoving"], "2.0 6.9 12.7": ["wai"], "23.1 23.9 31.7": ["hornet"], "-0.2 3.3 3.6": ["vocalized"], "4.4 5.8 10.8": ["utes"], "-4.8 5.1 19.6": ["citrusy"], "-4.2 2.6 10.6": ["stumpings"], "8.3 5.0 29.8": ["borscht"], "10.4 2.4 2.0": ["typesetting"], "12.8 10.9 16.6": ["stanchions"], "11.5 -2.2 -5.6": ["pressebox"], "3.2 5.5 3.0": ["interlinking"], "-9.3 8.5 5.0": ["plagiarize"], "2.0 3.3 8.5": ["harmonizes"], "3.7 17.1 3.7": ["frontbenchers"], "10.1 3.2 6.8": ["upstages"], "22.0 8.5 4.5": ["jumbotron"], "0.9 5.1 5.2": ["disasterassistance"], "-6.5 26.2 6.9": ["corpsmen"], "-1.1 1.2 7.1": ["choosers"], "0.1 3.5 14.1": ["kampung"], "9.2 10.3 10.4": ["abc"], "5.9 12.7 13.3": ["inhumanely"], "6.5 7.9 11.2": ["bas"], "-3.4 10.1 11.9": ["eatables"], "15.9 11.9 15.2": ["epically"], "0.8 3.6 1.6": ["comports"], "-4.9 8.6 10.0": ["cryoablation"], "10.1 2.2 14.5": ["grandmotherly"], "-0.3 6.2 17.0": ["shearers"], "2.9 6.4 13.2": ["jonesing"], "13.6 1.5 8.9": ["burbling"], "5.0 -0.5 2.6": ["radiographers"], "-0.7 -1.1 10.5": ["hwan"], "2.4 5.6 32.7": ["clambake"], "-4.1 0.1 9.2": ["roundtrips"], "8.7 8.2 9.4": ["bolter"], "18.5 11.1 9.5": ["greenwash"], "9.3 -2.7 12.7": ["zingy"], "11.8 -1.3 24.2": ["fritter"], "-6.8 1.6 8.2": ["hyperlipidemia"], "-1.2 20.7 2.5": ["dishonoring"], "10.6 4.1 2.4": ["squirms"], "11.7 5.1 13.1": ["trashcans"], "0.6 -4.5 6.7": ["jobbing"], "-3.9 10.0 15.9": ["photomask"], "-1.9 3.0 6.7": ["hypnotherapist"], "7.1 4.8 3.9": ["plumbs"], "11.0 6.7 10.5": ["sittin"], "7.3 5.2 3.1": ["bah", "reactivates"], "-2.7 37.4 9.3": ["betrayer"], "4.4 1.1 8.4": ["clampdowns"], "10.3 11.6 7.9": ["prat"], "4.0 9.8 9.2": ["dada"], "0.3 16.6 5.2": ["disrespectfully"], "1.3 12.2 6.9": ["burgle"], "-7.0 3.5 11.5": ["autocross"], "1.6 -0.6 29.9": ["tomatillos"], "9.0 13.7 3.8": ["cocooning"], "8.0 14.1 8.0": ["presciently"], "15.6 4.0 22.3": ["lolly"], "8.2 15.4 2.5": ["vandalization"], "16.2 11.9 13.7": ["twat"], "-0.3 14.3 10.1": ["razz"], "-6.4 14.7 3.4": ["tourniquets"], "3.1 -1.4 4.3": ["curvier"], "0.6 6.5 15.0": ["testis"], "9.4 0.9 6.1": ["foxed"], "-4.4 0.8 6.6": ["testwork"], "7.8 18.5 7.6": ["corrodes"], "-4.2 16.3 1.0": ["interrogates"], "3.9 -2.3 11.1": ["ec"], "-0.7 8.5 8.5": ["motorcyle"], "8.5 19.3 2.4": ["scorches"], "7.5 2.1 5.8": ["meg"], "-1.1 13.3 -10.1": ["repudiates"], "1.3 6.5 5.7": ["parentless"], "-3.9 -1.4 9.1": ["ropers"], "8.6 -1.6 4.6": ["cottoned"], "-4.9 13.3 1.8": ["checkposts"], "-1.9 23.8 13.0": ["invariable"], "-1.1 9.2 6.8": ["hews"], "8.4 19.5 13.4": ["illusionary"], "3.7 20.1 13.0": ["batman"], "3.4 10.8 8.7": ["antiestablishment"], "-0.2 8.1 10.4": ["homesteading"], "13.2 8.6 18.0": ["sludgy"], "-4.9 10.9 -1.2": ["unattributed"], "14.3 11.5 15.3": ["languidly"], "12.8 8.3 3.1": ["stubbing"], "8.3 4.7 7.1": ["brassiere"], "-1.8 4.6 -2.1": ["gadolinium"], "-0.0 11.1 6.7": ["bankrupts"], "-3.9 18.0 -2.2": ["instrumentalities"], "0.5 4.6 2.9": ["tidiness"], "10.1 16.0 15.2": ["simile"], "5.4 8.2 13.1": ["hella"], "8.9 8.2 8.4": ["lidar"], "-7.4 -0.9 8.7": ["postdocs"], "1.4 3.7 9.0": ["yardwork"], "11.2 8.4 21.3": ["macaws"], "-5.6 4.0 0.5": ["wordings"], "5.4 4.3 16.9": ["banquette"], "22.8 12.6 11.6": ["spidery"], "5.0 0.8 -4.3": ["unparallel"], "2.4 8.1 1.3": ["geocoding"], "7.9 14.2 4.1": ["effrontery"], "11.9 12.6 -0.8": ["reoriented"], "16.1 8.9 6.5": ["moneybags"], "1.2 10.9 7.5": ["mooned"], "11.5 4.6 5.3": ["reclines"], "-4.9 5.1 11.6": ["pitchy"], "-3.3 4.1 1.9": ["untypical"], "6.3 3.0 10.0": ["totting", "edmontonjournal"], "8.2 14.4 5.7": ["contrail"], "8.7 9.1 3.2": ["applecart"], "-1.6 21.9 0.6": ["insurrections"], "14.4 5.1 21.6": ["cactuses"], "-8.1 5.1 0.0": ["syncope"], "2.4 4.2 10.9": ["immigrations"], "8.6 5.1 3.8": ["wellwishers"], "-0.8 11.6 5.6": ["peccadilloes"], "4.5 -5.8 13.2": ["jun"], "13.1 -2.6 19.3": ["megaprojects"], "2.6 5.4 6.7": ["antismoking"], "9.0 25.0 6.1": ["footstep"], "4.3 15.3 13.8": ["granaries"], "10.3 5.3 17.9": ["healthiness"], "4.6 9.0 4.1": ["unsafely"], "21.8 9.8 12.9": ["gumming"], "5.8 9.5 -1.4": ["hoodwinking"], "9.1 15.2 8.7": ["sucky"], "24.3 3.4 6.9": ["bods"], "-6.3 3.8 8.7": ["ammonium"], "15.4 9.5 4.3": ["cellco"], "-2.2 -0.2 7.7": ["bibliographic"], "10.3 4.1 -2.5": ["leapfrogs"], "14.0 9.3 10.8": ["spattering"], "4.9 9.1 6.4": ["unrewarding"], "9.3 21.6 13.1": ["rapier"], "3.6 9.2 5.7": ["shakedowns"], "9.0 21.3 4.8": ["indescribably"], "-0.5 6.7 39.8": ["belugas"], "7.6 14.2 1.8": ["decontaminating"], "5.2 10.2 2.8": ["perturbations"], "-4.4 6.8 16.3": ["artesian"], "-4.4 4.9 4.6": ["remount"], "11.2 12.4 10.5": ["fucks"], "10.2 7.8 15.3": ["auroras"], "20.8 9.2 14.2": ["beanbags"], "4.4 6.1 11.6": ["schnapps"], "5.9 13.6 5.8": ["ungracious"], "3.2 7.9 7.9": ["boomeranged"], "-2.5 8.2 7.0": ["peritonitis"], "-3.6 16.9 6.2": ["modernizers"], "22.3 25.7 10.4": ["cybernetic"], "11.2 13.0 1.0": ["coltan"], "7.3 13.6 10.6": ["coalmines"], "6.8 12.2 8.5": ["nuff"], "0.4 0.2 8.7": ["unmetered"], "17.9 16.1 12.2": ["yeti"], "-1.7 3.3 45.9": ["paua"], "6.9 3.3 20.9": ["brogue"], "2.6 7.5 14.2": ["tobogganing"], "7.9 9.7 11.7": ["speedskaters"], "1.1 26.0 12.5": ["blitzer"], "3.2 6.7 -1.8": ["undisputedly"], "7.5 9.4 13.5": ["clubber"], "-2.4 7.4 7.0": ["mayorship"], "4.5 5.6 22.9": ["gourmands"], "12.7 6.0 5.2": ["shams"], "-0.1 3.1 9.0": ["folksinger"], "11.4 10.1 16.2": ["subcontinental"], "7.0 13.6 6.1": ["dimensionality"], "11.3 5.1 1.6": ["rort"], "2.5 -2.1 5.4": ["auctioneering"], "7.3 18.4 19.0": ["litterbugs"], "-4.4 9.0 8.4": ["upturns"], "7.7 6.1 13.2": ["ufc"], "0.2 20.2 10.8": ["disfavored"], "3.2 -3.5 1.2": ["chauffeuring"], "15.1 15.4 3.8": ["uselessly"], "-3.8 9.5 -1.6": ["ultracapacitor"], "4.7 -8.3 15.6": ["frizzy"], "13.6 3.7 6.4": ["malodorous"], "-3.7 15.9 6.6": ["reenacting"], "-16.6 3.2 5.7": ["continuances"], "-4.4 13.7 15.7": ["pruners"], "13.4 7.8 2.7": ["afer"], "14.9 6.1 4.7": ["spiriting"], "10.4 -1.0 1.9": ["modernistic"], "4.0 12.5 24.4": ["leaved"], "-0.8 12.7 19.1": ["campylobacter"], "-3.1 3.8 13.7": ["zeaxanthin"], "-1.9 3.8 10.3": ["cryptosporidium"], "-2.5 15.4 3.7": ["holstered"], "8.4 14.2 12.6": ["slashers"], "1.7 -1.5 9.0": ["perms"], "7.6 13.9 7.3": ["rouses"], "9.4 -3.5 5.0": ["como"], "1.9 3.9 6.3": ["cw"], "21.5 5.2 12.6": ["meccas"], "7.8 17.1 26.9": ["hyacinths"], "-0.4 2.8 18.8": ["loam"], "3.7 16.5 5.8": ["unequipped"], "-3.6 1.4 9.3": ["satang"], "5.0 12.4 14.0": ["neutrino"], "8.3 1.8 2.8": ["ecomagination"], "6.2 7.9 14.6": ["nodule"], "8.0 6.5 4.3": ["profilers"], "2.9 6.6 17.1": ["corns"], "27.0 2.6 16.3": ["emporiums"], "17.6 -0.1 17.5": ["slurped"], "5.9 16.3 2.0": ["crybabies"], "-0.7 6.1 21.3": ["antiquing"], "-2.9 7.4 1.3": ["meningococcal"], "9.2 -1.3 2.2": ["underpay"], "23.6 6.9 9.3": ["starburst"], "6.5 0.5 9.7": ["crackheads"], "5.9 8.9 -1.9": ["recasts"], "6.6 15.5 6.6": ["condescendingly"], "18.8 27.8 9.6": ["blasters"], "10.2 5.6 10.9": ["congressionally"], "5.4 14.6 0.2": ["demonizes"], "12.7 8.6 6.1": ["ubiquitously"], "11.7 8.4 10.5": ["lozenge"], "9.3 29.1 6.6": ["subjugating"], "-7.7 -0.5 12.3": ["contentiousness"], "-3.7 8.4 7.5": ["downshifts"], "1.3 4.9 1.9": ["micrometer"], "1.5 17.4 0.1": ["contrails"], "16.2 13.5 2.1": ["stickiest"], "-1.8 8.8 20.1": ["peninsulas"], "8.5 13.5 14.8": ["blubbering"], "7.1 4.8 -0.8": ["conjugated"], "2.7 8.1 16.8": ["supers"], "-0.2 3.3 24.6": ["sorbets"], "14.6 3.0 6.7": ["timeworn"], "13.0 17.8 12.9": ["foretelling"], "-6.4 -0.0 9.8": ["nonacademic"], "14.5 11.9 14.8": ["insta"], "-5.9 0.3 3.7": ["angiographic"], "6.4 6.1 16.2": ["ornithology"], "-0.9 0.6 52.5": ["finfish"], "13.1 6.3 15.0": ["chrysalis"], "-2.3 10.7 10.0": ["musts"], "6.8 5.5 14.2": ["parthenogenesis"], "2.4 10.6 12.5": ["backmarkers"], "-3.5 16.7 6.7": ["disavowal"], "-6.0 19.6 9.4": ["antagonisms"], "20.1 -0.7 6.9": ["blockbusting"], "-1.6 7.1 12.0": ["broaches"], "4.4 9.8 7.7": ["playdate"], "-2.2 9.5 8.6": ["parvovirus"], "1.1 9.5 8.5": ["occurence"], "-0.3 -1.4 7.4": ["microsurgery"], "-5.4 6.6 19.0": ["hapu"], "4.0 0.3 5.5": ["palaver"], "10.7 25.1 4.8": ["remorselessly"], "2.3 6.2 15.3": ["kefir"], "14.6 3.0 17.9": ["pushcarts"], "18.0 13.7 33.3": ["hammerhead"], "-1.9 -3.1 8.7": ["recs"], "-1.8 12.3 8.5": ["amblyopia"], "-4.0 12.2 8.0": ["stoploss"], "8.2 2.7 4.8": ["massager"], "6.3 9.9 12.4": ["tush"], "4.0 18.3 9.7": ["meaninglessness"], "-0.1 -3.6 -0.4": ["cofounders"], "0.7 15.4 24.4": ["pollinator"], "-9.4 9.0 5.3": ["ley"], "-3.3 3.2 -2.4": ["reasserts"], "20.9 -2.9 13.9": ["glo"], "15.5 10.6 12.2": ["armature"], "0.7 6.6 9.5": ["mordant"], "9.5 6.6 4.4": ["alphanumeric"], "0.6 -5.5 7.2": ["syndicators"], "-2.2 9.1 4.0": ["midstretch"], "-10.2 5.6 42.3": ["shellfishing"], "4.1 11.5 5.0": ["cleavages"], "2.4 0.9 6.1": ["dapagliflozin"], "3.9 8.4 7.8": ["oxygenate"], "1.8 5.9 19.6": ["fumigant"], "-6.1 7.1 8.3": ["carcinomas"], "1.9 11.3 6.9": ["enterprisewide"], "7.3 1.0 10.1": ["erectile"], "8.1 7.3 0.8": ["frontpage"], "-2.5 6.1 29.5": ["chilis"], "-7.9 3.0 12.5": ["dayrate"], "5.3 8.5 37.4": ["estuarine"], "-2.1 6.7 6.7": ["heritable"], "13.8 13.3 39.8": ["bullfrogs"], "7.6 14.2 6.0": ["deaden"], "-3.4 3.4 6.6": ["buyside"], "-9.9 3.3 11.2": ["kurtas"], "2.0 7.0 13.0": ["pegmatite"], "18.9 13.2 8.6": ["spaceman"], "7.1 -1.9 2.6": ["commodes"], "2.4 12.5 6.0": ["reciprocates"], "0.5 21.3 10.6": ["segregationists"], "13.6 13.0 32.1": ["shucking"], "-1.3 -2.1 8.9": ["deadlift"], "14.2 -2.0 13.1": ["athon"], "-0.9 14.8 1.2": ["wananchi"], "-2.1 1.7 35.1": ["lox"], "12.8 2.0 4.6": ["chattered"], "18.6 15.5 19.7": ["icicle"], "-6.7 4.7 18.3": ["healthfully"], "0.2 9.7 6.2": ["undeservedly"], "-8.1 6.1 3.7": ["osteopenia"], "6.4 13.6 23.7": ["coleus"], "-0.8 5.6 10.4": ["rockslides"], "11.2 5.3 4.8": ["troves"], "8.6 5.0 2.3": ["outduels"], "7.5 16.5 9.3": ["emasculating"], "2.1 5.4 4.7": ["slighter"], "1.9 15.4 5.6": ["coconspirator"], "-3.3 0.1 5.6": ["sportive"], "8.5 14.1 -0.8": ["scornfully"], "6.9 19.4 1.0": ["halfheartedly"], "6.8 11.7 11.8": ["towner"], "19.1 15.1 11.8": ["hexagon"], "8.8 0.3 9.5": ["enthusing"], "16.6 19.5 13.0": ["pinprick"], "-5.1 11.6 7.6": ["batterymate"], "7.9 -2.2 5.9": ["securitizing"], "11.1 4.3 11.3": ["jiving"], "0.9 7.0 9.0": ["soymilk"], "17.9 6.5 12.4": ["indigestible"], "5.5 14.3 7.6": ["keylogger"], "11.8 5.5 8.6": ["choirboy"], "12.5 17.0 4.5": ["gloomily"], "2.6 21.2 10.3": ["reoccupation"], "5.1 0.5 6.4": ["relaid"], "4.5 2.7 0.1": ["sportscars"], "-0.9 22.2 4.2": ["flashover"], "5.1 10.3 10.1": ["cyberstalking"], "9.9 6.7 0.7": ["fron"], "-0.7 7.0 27.9": ["seedless"], "-1.8 12.6 4.5": ["gliomas"], "4.6 -0.1 -3.7": ["ipods"], "2.1 7.2 2.2": ["remonstrate"], "-1.8 11.7 0.7": ["drillhole"], "8.3 9.1 3.0": ["fascinatingly"], "0.9 7.3 8.6": ["supersub"], "2.6 12.1 14.2": ["snowfields"], "9.6 9.4 5.0": ["zinged"], "2.5 8.7 10.2": ["fingerpointing"], "8.7 4.2 14.3": ["equitisation"], "5.0 16.3 11.3": ["ridgelines"], "0.2 13.7 11.7": ["unequally"], "13.2 4.1 6.3": ["effexor"], "10.0 10.3 8.0": ["buggered"], "6.3 22.8 4.3": ["destructively"], "4.5 14.6 6.5": ["territorially"], "3.5 2.5 6.0": ["regales"], "9.1 13.5 2.4": ["despatching"], "-6.8 0.9 3.3": ["pharmacodynamic"], "0.6 19.4 11.5": ["ulterior"], "-0.6 14.9 24.3": ["didymo"], "0.5 -1.8 3.9": ["rt"], "-9.7 -1.7 15.3": ["wools"], "16.5 5.0 1.2": ["bythe"], "-2.0 3.7 -1.0": ["incentivising"], "4.3 5.8 10.9": ["piazzas"], "4.2 4.0 11.3": ["slj"], "18.5 4.7 12.7": ["slopping"], "-0.3 0.4 4.8": ["hijabs"], "-0.3 6.3 2.5": ["supercritical"], "4.0 10.0 6.2": ["unethically"], "20.1 10.7 10.9": ["slithers"], "0.7 19.2 7.0": ["privations"], "13.3 10.4 12.6": ["barstools"], "10.9 -7.1 9.5": ["placentas"], "5.4 18.7 9.1": ["adivasis"], "-3.8 9.7 6.7": ["determinable"], "-3.6 19.1 8.6": ["sovereigntist"], "1.6 7.9 -3.3": ["nad"], "6.9 14.7 5.1": ["smartness"], "3.7 -4.9 9.0": ["lhp"], "-9.1 8.6 -1.0": ["polygraphs"], "2.3 5.0 1.8": ["submitter"], "5.0 7.6 19.9": ["birdlife"], "2.8 4.6 4.9": ["highlife"], "11.0 7.5 19.3": ["grater"], "0.6 1.4 9.6": ["travelogues"], "11.2 11.4 9.3": ["cyclically"], "-2.7 6.5 9.7": ["portlets"], "6.1 7.5 14.9": ["gravatar"], "-1.6 5.5 10.5": ["ducats"], "-6.1 5.6 5.1": ["extemporaneous"], "-1.0 5.9 8.7": ["proposer"], "0.1 14.6 4.8": ["veiling"], "11.7 9.1 -6.4": ["monetising"], "-4.7 9.8 10.6": ["lymphatic"], "-9.9 0.2 4.8": ["hypogonadism"], "6.2 12.2 10.6": ["aerialist"], "7.5 4.6 6.3": ["grandniece"], "12.3 2.5 4.3": ["steepened"], "10.8 23.3 2.9": ["horrifyingly"], "-10.6 -3.2 -0.4": ["valproate"], "13.9 4.8 8.3": ["technophiles"], "22.1 8.4 32.5": ["tadpole"], "8.9 4.7 25.7": ["gristle"], "-3.2 4.4 4.5": ["carriageways"], "-2.4 -0.3 6.3": ["sketchbooks"], "2.6 14.2 12.7": ["supercilious"], "-0.3 -0.7 13.2": ["lavishness"], "11.8 13.6 -10.2": ["exalting"], "-3.4 16.1 4.3": ["lucidly"], "3.2 5.1 6.5": ["caprices"], "16.8 13.1 11.6": ["jollies"], "6.4 8.6 9.3": ["thriftiness"], "0.2 5.2 8.8": ["comprehensives"], "-5.1 15.3 5.9": ["sideout"], "10.8 -2.9 2.2": ["creches"], "11.9 7.4 6.0": ["doddle"], "2.9 11.1 24.1": ["seaway"], "11.5 26.4 3.4": ["handmaiden"], "12.2 3.1 25.8": ["stevedores"], "16.5 15.2 9.4": ["flaying"], "-1.0 -0.3 14.3": ["nasally"], "6.7 5.6 14.6": ["studly"], "0.8 7.0 4.5": ["monocytes"], "11.5 -3.5 2.9": ["vinyls", "dyehouse"], "11.4 4.4 15.0": ["george"], "1.7 7.3 -3.3": ["unspecific"], "15.1 5.6 19.8": ["yew"], "7.1 4.8 -2.3": ["speculatively"], "4.5 -3.3 11.4": ["bioethicists"], "15.6 19.9 22.5": ["arthropods"], "12.6 8.1 19.9": ["mmm"], "0.0 8.0 7.0": ["gastritis"], "4.4 9.4 25.7": ["gourmand"], "-1.9 23.8 4.4": ["retaliations"], "9.8 3.4 20.9": ["rawhide"], "9.1 5.6 6.5": ["witha"], "7.3 13.2 2.8": ["amasses"], "15.0 5.9 15.1": ["brainiacs"], "4.5 9.6 5.9": ["mishandle"], "0.6 3.8 7.7": ["despairs"], "3.6 20.3 3.0": ["delude"], "8.0 3.6 6.7": ["delhi"], "10.8 18.2 6.5": ["divining"], "13.0 4.1 8.9": ["cinderblocks"], "4.1 9.8 13.2": ["lightheartedly"], "5.0 0.8 13.2": ["foreleg"], "-3.7 0.2 -7.2": ["transfering"], "-4.5 10.4 -0.8": ["sadden"], "15.4 9.1 7.7": ["gurgle"], "10.7 -0.8 -2.0": ["thecompany"], "15.2 10.5 10.1": ["neverending"], "-2.6 6.4 -10.3": ["negations"], "-7.7 9.8 1.6": ["creditability"], "8.4 21.8 10.9": ["autocracies"], "0.1 25.2 31.1": ["invasives"], "9.5 18.5 10.8": ["teleports"], "0.1 0.9 0.7": ["philharmonic"], "3.8 12.0 11.4": ["machinima"], "18.6 15.3 39.4": ["bullfrog"], "-2.0 0.3 4.0": ["criminalist"], "6.1 15.6 4.1": ["deified"], "3.7 -3.0 11.1": ["toolboxes"], "0.9 5.5 9.3": ["landbank"], "3.4 1.8 15.6": ["shisha"], "-0.4 4.8 13.4": ["dishware"], "-1.7 3.8 12.3": ["warmhearted"], "5.1 13.7 3.0": ["wifey"], "-3.0 13.5 6.1": ["potently"], "-4.6 22.9 13.1": ["dogmatism"], "-12.9 -1.4 4.8": ["provisionals"], "12.8 5.2 7.0": ["snuggly"], "-1.3 0.7 3.9": ["childrenswear"], "7.7 3.4 6.6": ["whetting"], "11.8 12.7 36.7": ["egret"], "11.2 6.5 5.4": ["cubby"], "3.4 1.0 -1.3": ["sexualization"], "2.3 0.7 5.2": ["satirizes"], "0.2 -4.5 0.8": ["acceptors"], "9.1 13.7 0.9": ["multitaskers"], "4.6 0.3 -7.1": ["echocardiograms"], "21.9 5.7 5.3": ["bendy"], "0.9 2.5 7.6": ["adiponectin"], "-9.0 7.4 9.7": ["ezine"], "9.0 -3.2 1.3": ["glossies"], "-5.2 14.5 4.8": ["classicist"], "7.3 11.7 27.4": ["crocus"], "8.4 14.0 2.9": ["backscatter"], "0.6 7.8 26.9": ["snorkelers"], "7.6 4.5 9.2": ["nova"], "9.1 23.8 7.0": ["isometric"], "16.2 18.0 5.4": ["detaches"], "-2.2 7.0 6.9": ["underachieve"], "12.8 5.1 -1.9": ["easterners"], "4.3 0.9 4.2": ["speedup"], "1.2 0.9 3.6": ["ceftobiprole"], "6.1 3.5 8.6": ["troubadours"], "-2.4 1.4 33.5": ["tempeh"], "16.9 12.4 0.7": ["brainwaves"], "0.3 6.7 4.9": ["arroyo"], "2.0 24.3 0.9": ["gendarme"], "-2.2 7.3 6.7": ["idiomatic"], "-10.7 11.0 14.7": ["kumite"], "0.4 6.5 9.8": ["jeepneys"], "7.2 1.1 27.0": ["waka"], "13.1 35.8 4.5": ["warzone"], "-4.6 11.9 4.9": ["retinoblastoma"], "-7.3 12.8 8.7": ["unassigned"], "5.9 7.2 7.9": ["cartographers"], "-2.8 11.6 3.2": ["humorists"], "-1.4 7.3 21.7": ["graziers"], "1.1 3.5 5.3": ["cation"], "10.4 1.6 24.2": ["woodchip"], "1.4 -0.3 4.7": ["thoughout"], "0.9 14.3 7.7": ["strategising"], "4.3 2.6 0.4": ["tabbing"], "3.6 6.1 16.1": ["breakages"], "1.9 1.6 2.4": ["encash"], "11.4 3.2 -1.5": ["recapitalised"], "7.0 -7.0 -0.5": ["sucessful"], "8.4 8.7 3.6": ["theremin"], "-13.9 21.0 13.8": ["redeployments"], "8.7 1.9 17.3": ["cluck"], "3.3 7.1 8.5": ["shirtsleeves"], "12.5 8.2 3.0": ["rearranges"], "1.2 3.4 6.3": ["multiplexers"], "2.9 -0.7 4.2": ["polkas"], "-2.3 1.1 -5.2": ["seconding"], "-2.0 1.2 8.3": ["attires"], "-5.6 10.6 9.6": ["transborder"], "15.2 0.3 18.2": ["tufted"], "16.0 6.5 13.5": ["wondrously"], "13.2 4.2 11.7": ["ropey"], "12.5 2.3 8.1": ["squawked"], "7.1 6.1 19.9": ["stenciling"], "15.4 7.8 14.2": ["megalopolis"], "3.2 15.2 26.3": ["foragers"], "2.3 9.9 18.4": ["flagger"], "10.0 12.0 16.1": ["grouch"], "-1.7 12.5 9.5": ["featherweights"], "-1.9 20.0 5.2": ["waterboard"], "9.9 -8.9 6.0": ["anda"], "9.1 6.5 8.7": ["mesas"], "14.7 5.9 17.9": ["glasshouse"], "-2.3 10.5 10.6": ["soulfulness"], "4.6 15.5 13.5": ["phage"], "-3.2 8.7 -0.0": ["tefillin"], "4.4 19.2 9.4": ["infuriatingly"], "11.2 5.8 3.0": ["instore"], "13.6 30.0 9.5": ["accursed"], "1.5 -0.4 9.8": ["pu"], "6.5 -7.8 2.2": ["toiletry"], "3.5 1.2 5.2": ["sadomasochism"], "4.9 9.2 13.8": ["moneylender"], "7.2 6.7 8.8": ["berg"], "15.8 0.9 20.8": ["swags"], "-1.0 1.1 1.6": ["lodgement"], "8.6 6.1 16.1": ["applique"], "0.9 5.6 7.0": ["parses"], "0.2 -0.4 7.8": ["encephalopathy"], "-9.5 7.4 12.5": ["ghazal"], "4.1 7.4 1.6": ["watchmaking"], "4.5 11.6 4.5": ["motorcar"], "-9.8 8.7 4.5": ["netbacks"], "8.6 6.7 13.9": ["blotchy"], "19.6 5.1 7.5": ["pitchmen"], "5.9 0.6 6.1": ["admonishments"], "14.0 6.3 18.1": ["enameled"], "6.2 22.4 1.7": ["infringer"], "1.3 9.5 2.3": ["mispricing"], "11.1 6.6 28.6": ["whitecaps"], "1.6 4.9 3.3": ["distil"], "4.6 -1.1 15.6": ["timbered", "blueswoman"], "-5.9 14.8 5.4": ["historiography"], "-11.7 11.7 -8.8": ["prosecutable"], "16.2 10.6 13.9": ["diaphanous"], "7.8 1.2 12.6": ["twofer"], "8.7 16.1 12.3": ["unkindly"], "-3.4 1.8 9.6": ["orthodontists"], "11.5 31.7 12.3": ["vassal"], "4.6 10.9 11.7": ["raj"], "-4.2 13.9 9.8": ["ballhandlers"], "14.3 16.4 12.4": ["wanker"], "14.2 17.0 12.7": ["millenniums"], "-5.5 11.4 5.0": ["strongside"], "10.6 5.9 9.9": ["suburbanite"], "-0.3 -0.2 14.6": ["columbarium"], "8.4 12.9 13.5": ["reddest"], "-9.2 9.1 -0.3": ["impute"], "-10.0 2.0 1.9": ["floorplans"], "4.3 0.6 8.4": ["boozed"], "-0.5 4.6 -0.1": ["teetotal"], "6.7 7.8 0.0": ["sanitarium"], "0.0 11.1 8.6": ["subsidiarity"], "-1.4 15.8 -2.2": ["astonishes"], "7.9 12.7 0.3": ["teleservices"], "2.3 7.5 -2.5": ["glamorizing"], "15.7 13.6 34.1": ["finned"], "18.3 3.7 6.1": ["sheikdom"], "8.1 12.8 3.6": ["chakras"], "18.6 16.9 12.5": ["limply"], "4.0 6.5 6.3": ["commentate"], "8.4 0.2 3.3": ["pos"], "11.4 9.1 6.2": ["whorehouse"], "14.4 5.6 24.1": ["fishnet"], "-11.5 9.7 8.6": ["calibers"], "3.0 0.0 9.5": ["segueing"], "6.4 2.3 3.6": ["gb"], "4.0 -0.6 -3.8": ["ppi"], "10.3 0.4 22.1": ["ironwork"], "-1.9 14.0 4.8": ["inductance"], "-0.8 16.5 1.8": ["effectual"], "12.8 9.8 7.8": ["flay"], "8.1 3.1 2.7": ["indecently"], "1.9 3.2 23.2": ["paninis"], "2.0 3.7 6.6": ["freestyler"], "-4.3 6.1 1.6": ["neurobiological"], "6.0 11.8 12.2": ["guidepost"], "7.4 8.5 24.2": ["bluebells"], "0.4 8.0 15.5": ["histones"], "0.6 5.8 10.3": ["lamas"], "6.8 7.0 13.7": ["dyspepsia"], "7.7 22.0 8.6": ["concussive"], "1.3 2.0 9.4": ["playbill"], "-9.5 5.0 2.8": ["leu"], "5.4 13.3 3.6": ["birthplaces"], "14.4 11.6 12.3": ["flowerpot"], "5.9 12.2 1.8": ["inquisitiveness"], "3.8 1.3 9.8": ["vertebral"], "5.3 11.1 10.2": ["nunnery"], "2.9 2.1 3.4": ["rial"], "3.4 9.0 6.8": ["earache"], "-0.1 3.8 9.1": ["horticulturalist"], "4.0 4.5 5.7": ["wideman", "andnetwork"], "12.2 7.1 12.1": ["colonnade"], "18.6 10.1 9.8": ["humped"], "-5.0 5.4 8.4": ["timeslots"], "2.7 10.0 -2.6": ["ionized"], "3.2 4.0 11.8": ["headcounts"], "-2.4 7.0 19.2": ["teu"], "-5.9 5.0 10.1": ["immunohistochemistry"], "-1.8 21.2 9.7": ["enmities"], "10.7 23.3 9.1": ["villainess"], "-4.9 19.2 5.0": ["irreligious"], "8.5 -1.2 6.1": ["subsists"], "6.2 1.4 10.1": ["slake"], "14.4 7.6 6.7": ["identikit"], "11.8 16.7 6.1": ["hypnotizing"], "1.0 -0.5 9.5": ["endothelial"], "7.2 3.2 2.3": ["ck"], "7.6 14.9 12.3": ["egghead"], "-5.3 3.4 10.9": ["shutoffs"], "-0.6 7.6 5.1": ["steeping"], "7.7 2.9 7.6": ["rick"], "-12.2 12.8 3.3": ["exegesis"], "12.4 9.4 19.3": ["ridged"], "8.6 1.6 -2.5": ["industrys"], "15.3 23.9 10.4": ["jackal"], "-10.9 1.1 7.0": ["endocrinologists"], "6.0 18.0 3.3": ["triumphalist"], "6.3 14.7 10.0": ["strobes"], "3.9 6.4 14.0": ["zipline"], "5.0 3.2 31.6": ["paneer"], "8.1 4.2 11.3": ["crackly"], "4.7 7.7 -4.3": ["exorcising"], "3.4 4.1 10.9": ["sponging"], "-3.0 13.3 -1.2": ["eulogize"], "1.9 22.1 3.2": ["despising"], "8.1 8.8 5.3": ["hyperventilate"], "2.2 5.9 7.8": ["uprated"], "6.0 11.7 6.4": ["straightjacket"], "-11.0 -0.4 4.2": ["locums"], "-0.9 14.6 15.5": ["glades"], "9.4 12.5 6.3": ["conjugate"], "8.7 14.4 13.1": ["gerrymander"], "-13.9 4.8 2.5": ["caucused"], "1.0 10.1 7.0": ["jetway"], "-6.9 -1.7 4.0": ["memantine"], "10.1 6.9 9.1": ["firesale", "dhols"], "6.1 9.6 15.5": ["shorty"], "4.9 11.1 1.0": ["boondocks"], "9.1 7.6 13.5": ["goring"], "0.9 13.1 3.7": ["presuppose"], "-7.5 1.9 11.1": ["mucositis"], "5.0 4.3 9.6": ["beatboxing"], "4.2 6.0 25.5": ["shoreside"], "12.1 26.4 10.3": ["bulwarks"], "-4.3 1.9 -1.4": ["epidurals"], "10.1 9.9 9.8": ["scarfs"], "9.8 9.7 5.9": ["sharers"], "-5.0 10.2 14.7": ["tannic"], "10.8 12.1 11.4": ["grossest"], "3.5 10.6 8.8": ["eves"], "-0.4 4.5 8.7": ["teambuilding"], "-2.6 21.2 0.2": ["underrate"], "-2.7 1.6 8.8": ["predraft"], "1.9 15.6 10.0": ["gunrunning"], "-2.0 6.4 2.7": ["newsfeed"], "1.9 25.3 0.3": ["eavesdroppers"], "18.2 0.2 3.3": ["paperweights"], "1.8 9.9 13.7": ["neurones"], "16.2 20.1 23.5": ["gonads"], "22.4 3.5 13.4": ["birdcage"], "-0.1 14.9 9.8": ["acclimatized"], "6.0 10.8 7.5": ["nigeria"], "5.3 -5.5 3.8": ["sus"], "6.6 2.5 8.2": ["mtn"], "-1.5 15.0 3.1": ["invectives"], "-2.2 11.6 -1.4": ["touchpoints"], "-5.1 17.0 8.9": ["hydroplaning"], "-0.9 2.8 13.0": ["mummification"], "-4.0 15.8 12.1": ["malingering"], "4.1 0.7 13.4": ["manes"], "3.1 9.1 1.2": ["tangibles"], "10.3 10.8 11.1": ["presaging"], "-11.9 4.7 6.9": ["weatherized"], "-0.9 6.2 4.9": ["stimulatory"], "-1.3 21.8 13.2": ["bacteriological"], "5.1 12.5 3.3": ["childishly"], "-12.4 -1.8 4.6": ["reappointments"], "15.5 10.1 7.2": ["colloquially"], "6.3 4.2 7.8": ["jpeg"], "-6.7 12.4 7.2": ["authorial"], "14.1 19.3 7.4": ["crudest"], "14.5 7.3 9.5": ["vaporware"], "-1.8 11.6 -1.4": ["reconfirming"], "4.8 6.8 18.0": ["kaolin"], "-0.8 8.7 9.8": ["coarseness"], "6.9 14.0 8.6": ["centurions"], "-7.1 3.3 -1.3": ["parenteral"], "20.9 13.2 12.5": ["torchlight"], "-2.4 6.4 4.4": ["underexplored"], "17.4 5.7 7.3": ["wreathed"], "-4.1 6.4 13.2": ["remodeler"], "0.1 4.2 0.7": ["noticable"], "5.4 8.2 3.3": ["warhorses"], "4.2 8.4 6.4": ["presentational"], "-4.8 15.6 -3.1": ["slighting"], "-4.3 6.1 12.4": ["bouldering"], "-6.6 3.2 -2.7": ["runtimes"], "6.3 13.6 2.8": ["modders"], "-0.7 10.6 1.7": ["shush"], "3.5 19.7 4.2": ["extremis"], "-2.2 5.7 6.3": ["albuterol"], "9.1 5.1 14.2": ["sixpence"], "15.4 -3.7 7.7": ["sudsy"], "-1.4 14.2 7.9": ["chastisement"], "8.6 6.9 1.1": ["piezo"], "-7.7 -1.1 -4.9": ["neuropsychological"], "-2.3 6.9 19.8": ["sculling", "kinnow"], "9.4 11.4 19.0": ["creeper"], "4.3 -2.8 -1.5": ["microfiche"], "6.6 8.4 8.1": ["misbranded"], "1.1 7.0 4.5": ["iovation"], "16.8 18.0 4.4": ["godforsaken"], "-7.4 11.8 13.9": ["recreationists"], "6.6 6.8 8.2": ["ingenuous"], "7.5 19.0 7.1": ["incantation"], "-2.8 5.8 1.0": ["undistributed"], "4.9 6.9 3.1": ["pervasively"], "9.3 19.2 3.5": ["ravished"], "-5.0 10.0 7.1": ["accountabilities"], "9.9 -5.0 -2.7": ["companyas"], "7.9 10.7 11.4": ["snakebit"], "4.7 20.3 9.5": ["homos"], "1.8 11.1 1.5": ["fluoroscopy"], "-3.3 5.0 4.0": ["abstainers"], "1.9 4.2 1.6": ["twiddle"], "1.1 3.9 4.7": ["talkie"], "7.2 6.3 7.1": ["footrest"], "5.2 14.1 10.2": ["digg"], "3.1 3.7 6.8": ["hogtied"], "0.4 11.3 6.0": ["overestimation"], "16.0 1.8 6.0": ["seismograph"], "0.3 7.7 39.5": ["endive"], "2.0 27.0 2.4": ["ummah"], "1.9 0.6 5.8": ["admixture"], "3.0 18.4 9.9": ["instigates"], "8.8 4.3 12.8": ["huffy"], "-6.9 -0.5 5.1": ["etanercept"], "21.1 17.3 7.2": ["carmaking"], "8.5 3.0 8.7": ["kb"], "-6.2 3.6 3.3": ["duloxetine"], "-0.3 14.5 1.3": ["redial"], "11.5 8.1 5.7": ["nokia"], "2.5 5.9 6.2": ["copiously"], "10.2 13.0 2.8": ["liquidates"], "-4.4 5.5 11.5": ["bindery"], "0.6 9.5 1.0": ["peleton"], "9.6 10.6 25.7": ["wattle"], "10.5 4.6 0.8": ["auf"], "0.8 17.5 5.7": ["misbehaves"], "-3.9 14.5 7.5": ["abductee"], "-6.2 1.2 0.6": ["payees"], "6.3 13.4 7.4": ["recalculating"], "-5.8 5.1 1.2": ["incent"], "23.3 8.4 7.3": ["wonderkid"], "-6.0 6.8 4.5": ["hematologist"], "0.4 4.3 11.1": ["fluorescents"], "1.7 4.4 8.3": ["mountings"], "-7.4 3.9 4.0": ["midazolam"], "9.3 14.6 14.8": ["hatchets"], "9.1 6.8 14.2": ["composited"], "6.2 12.2 9.7": ["unnerves"], "4.8 20.7 20.5": ["macrophage"], "21.1 22.8 3.5": ["pilotless"], "7.5 1.7 8.8": ["jetsam"], "3.2 2.5 -1.5": ["thankyou"], "0.5 2.3 7.9": ["condensates"], "-3.5 30.6 3.2": ["overwatch"], "6.4 6.4 19.7": ["crossbreeding"], "6.6 -4.5 3.9": ["cond"], "9.2 -0.8 -3.0": ["seatbacks"], "-1.1 7.5 2.7": ["singh"], "4.3 12.4 -0.8": ["chatbox"], "-0.6 10.2 15.5": ["demodulator"], "16.6 -0.6 4.6": ["somnolent"], "0.4 11.1 8.2": ["fruitfully"], "1.6 8.3 20.4": ["boreal"], "10.2 11.8 37.3": ["lunker"], "7.3 2.1 3.0": ["reengineered"], "4.8 2.6 1.9": ["peformance"], "-3.8 -0.2 8.4": ["monomer"], "1.2 0.4 -5.7": ["videoconferences"], "5.3 11.3 5.3": ["reflectance"], "3.6 7.5 5.9": ["wetted"], "5.7 15.6 2.6": ["unswervingly"], "-7.1 9.2 0.3": ["breathability"], "-4.4 13.1 9.1": ["sulfonylurea"], "4.5 7.6 2.6": ["oscillates"], "0.1 2.0 1.3": ["evinces"], "-8.6 4.2 4.2": ["transboundary", "kebeles"], "3.4 11.5 9.8": ["suppleness"], "5.3 5.9 13.3": ["yokozuna"], "14.3 15.0 14.1": ["arab"], "2.7 18.1 22.1": ["larvicide"], "7.5 13.1 8.9": ["cornball"], "6.6 6.3 11.0": ["tastemaker"], "29.6 9.0 6.9": ["dynamos"], "1.4 0.8 16.7": ["pumice"], "-3.0 13.8 14.6": ["neediness"], "-0.5 3.0 6.1": ["aprotinin"], "-5.9 4.3 7.9": ["imprisonments"], "11.2 8.2 9.2": ["arturc"], "24.0 14.2 21.1": ["prow"], "-2.9 4.2 4.7": ["labia"], "16.3 5.3 11.7": ["regally"], "1.7 11.0 8.0": ["severly"], "-2.8 -1.8 -2.6": ["tapeless"], "16.4 5.7 36.1": ["toothsome"], "6.1 -3.3 6.3": ["ree"], "4.8 13.7 28.7": ["forsythia"], "-3.9 6.4 4.1": ["placegetters"], "-8.2 4.4 5.6": ["circumcise"], "4.2 -3.6 9.4": ["gushy", "detalles"], "3.0 3.3 13.9": ["brian"], "4.6 4.8 5.0": ["bapineuzumab"], "12.5 -1.4 8.1": ["multipart"], "-8.5 0.1 5.6": ["honourees"], "4.6 4.7 5.6": ["pipefitter"], "1.4 9.6 14.5": ["itchiness"], "-2.0 9.3 14.2": ["fibroid"], "8.6 16.8 6.6": ["embroil"], "-3.8 12.7 15.0": ["refreeze"], "8.3 1.7 50.3": ["scampi"], "-7.0 8.1 8.8": ["verbals"], "5.4 9.2 12.2": ["philosophizing"], "5.3 13.4 3.5": ["surmountable"], "8.1 5.3 2.0": ["ejects"], "2.1 -0.8 10.6": ["gardened"], "1.8 4.9 13.1": ["chenille"], "4.2 6.5 5.2": ["prompter"], "-1.4 16.4 7.3": ["diffidence"], "-0.8 10.1 6.8": ["epitestosterone"], "-3.3 9.6 3.3": ["underutilization"], "-2.5 2.9 9.8": ["subletting"], "6.2 13.4 6.1": ["unconscionably"], "-7.7 9.9 3.9": ["unfurnished"], "-1.4 10.5 -0.0": ["chargesheets"], "15.7 17.1 8.0": ["blandishments"], "-3.5 4.8 24.7": ["precooked"], "22.9 12.4 18.8": ["slithery"], "15.4 4.3 3.7": ["teddies"], "4.8 11.9 5.0": ["strategized"], "20.5 -1.3 4.1": ["pavillion"], "-3.4 7.7 6.5": ["pastoralist"], "-3.9 12.2 9.5": ["teachable"], "4.3 4.8 10.6": ["slm"], "7.0 10.0 -0.4": ["sportingly"], "-2.6 2.1 4.7": ["reno"], "11.2 9.4 18.4": ["aerialists"], "6.7 5.9 9.7": ["tremulous"], "3.6 -0.3 8.6": ["unspool"], "1.9 4.2 13.4": ["lushness"], "-3.7 0.2 4.3": ["matriculants"], "-0.5 -0.8 15.6": ["banda"], "10.1 9.7 16.8": ["innit"], "-6.7 7.8 6.3": ["sinbinned"], "-0.1 7.5 5.5": ["microeconomic"], "5.5 10.3 12.7": ["moshing"], "5.4 14.4 7.3": ["talismans"], "-0.1 2.6 1.3": ["guarana"], "-2.0 7.9 0.0": ["erosions"], "12.0 5.6 9.1": ["stupendously"], "6.2 1.4 6.5": ["phew"], "-3.5 0.2 10.4": ["myopathy"], "6.1 4.1 5.1": ["dotage"], "4.4 13.4 29.7": ["phlox"], "7.1 10.2 12.5": ["bitmap"], "-1.2 26.8 5.9": ["dacoit"], "-5.1 10.9 9.0": ["verbosity"], "8.7 24.5 6.2": ["plowshares"], "8.1 -0.1 18.4": ["concs"], "-1.2 12.3 21.7": ["spinnakers"], "5.0 14.9 16.4": ["staredown"], "-6.2 -7.4 4.5": ["adjudications"], "6.1 6.5 5.8": ["cinemagoers"], "-1.9 6.3 0.4": ["conclaves"], "4.3 0.8 7.1": ["wih"], "-2.4 17.2 4.3": ["trainable"], "0.7 9.5 1.8": ["cemetary"], "5.4 10.6 20.7": ["flukey"], "2.3 5.2 8.8": ["rez"], "15.6 7.7 15.3": ["pallor"], "-5.9 7.7 4.5": ["cannula"], "15.3 2.4 32.2": ["stilt"], "-0.7 -0.6 12.8": ["oligonucleotide"], "4.3 1.2 8.0": ["hangup"], "-5.2 4.6 3.6": ["neurovascular"], "8.3 9.1 15.3": ["handclaps"], "-10.6 4.7 11.6": ["kashrut"], "3.4 -0.4 -1.6": ["installable"], "-0.5 9.4 -3.2": ["knowledgeably"], "-5.1 14.9 7.9": ["predetermine"], "11.7 6.9 -1.3": ["bisect"], "4.8 1.1 7.5": ["hotpants"], "1.0 8.0 6.8": ["conjectured"], "-8.1 9.7 7.0": ["zanamivir"], "-7.0 2.1 -1.8": ["degreed"], "-2.2 15.9 7.4": ["oppositionists"], "-0.6 -4.2 1.0": ["licensable"], "-4.0 -3.8 4.8": ["relaxations"], "-5.9 -3.9 6.2": ["hoarseness"], "16.7 7.9 11.5": ["wingless"], "12.5 17.7 11.5": ["imperiously"], "-4.0 13.8 3.5": ["introverts"], "20.0 4.4 38.8": ["seahorse"], "9.8 8.0 11.6": ["sendup"], "11.7 8.7 5.5": ["douses"], "17.0 21.9 5.4": ["electrocute"], "4.3 12.5 34.0": ["molt"], "-4.9 12.6 10.7": ["puffiness"], "4.5 2.8 6.4": ["binning"], "14.3 6.8 9.2": ["cashpoint"], "4.1 5.5 48.2": ["croakers"], "8.1 28.3 3.7": ["usurpers"], "14.8 12.6 8.5": ["touchable"], "7.1 11.8 3.8": ["whupped"], "-3.8 11.2 5.8": ["economizing"], "-1.7 18.1 2.6": ["confessor"], "7.0 14.1 13.6": ["balloonist"], "7.1 11.0 19.7": ["seafarer", "systematics"], "9.3 4.8 -1.1": ["bumming"], "2.9 10.9 7.6": ["willfulness"], "9.7 10.9 17.0": ["woodcarver"], "4.8 11.3 6.7": ["prettiness"], "-2.5 3.0 4.3": ["dt"], "1.4 1.8 8.2": ["friended"], "-2.5 0.0 9.1": ["tellurium"], "-8.3 3.7 18.8": ["chardonnays"], "-0.3 9.1 19.9": ["seaplanes"], "5.5 17.1 4.8": ["reductionist"], "-3.9 7.1 1.6": ["microgeneration"], "0.3 -0.6 -1.0": ["biobased"], "3.7 4.4 10.5": ["bellhop"], "9.9 1.4 20.4": ["pushcart"], "6.0 14.7 7.5": ["unasked"], "2.6 2.3 27.6": ["tandoori"], "13.6 25.7 6.6": ["plunderers"], "20.4 9.4 18.9": ["gluttons"], "15.2 5.4 2.5": ["bisecting"], "7.3 7.8 18.0": ["greengrocer"], "-4.9 7.8 6.4": ["outstate"], "-10.0 10.7 -8.4": ["redesignated"], "2.8 5.8 17.4": ["emulsified"], "11.2 -5.2 5.9": ["mariachis"], "6.4 2.9 26.3": ["keiki"], "5.8 9.2 -4.0": ["poeple"], "-1.3 4.8 9.6": ["cutover"], "3.9 22.4 14.6": ["mercantilist"], "-8.8 11.1 17.0": ["sulfites"], "4.2 3.7 28.1": ["pierogies"], "1.8 -2.2 2.1": ["ana"], "2.7 13.1 5.7": ["oxidizing"], "10.4 -3.1 10.9": ["chunkier"], "-1.8 15.5 10.0": ["premonitions"], "-0.4 15.9 0.3": ["propensities"], "-0.9 1.4 1.6": ["retractions"], "-7.5 11.5 -5.2": ["narrations"], "3.0 4.8 10.8": ["sonics"], "10.1 4.6 0.8": ["paraplegics"], "9.1 11.8 10.1": ["scummy"], "8.4 6.7 13.9": ["pecks"], "13.7 3.9 -5.8": ["unveilings"], "-4.6 8.7 4.6": ["rubberstamp"], "10.1 2.9 2.4": ["supplants"], "2.7 3.2 6.1": ["redecoration"], "9.4 17.6 8.6": ["homeboys"], "11.1 12.7 12.1": ["networkers"], "8.2 -0.5 8.0": ["sha"], "-3.4 11.2 11.0": ["districting"], "-4.3 12.9 12.9": ["winterizing"], "4.5 11.4 6.4": ["baptizing"], "3.2 -0.6 12.1": ["microlending"], "-0.4 8.9 3.8": ["dimmable"], "6.6 16.2 1.6": ["irrefutably"], "4.5 1.5 11.0": ["disapprovingly"], "-2.7 6.4 7.3": ["unadvertised"], "4.3 -1.3 6.3": ["reutilization"], "4.7 15.3 9.9": ["blinker"], "1.7 11.7 1.6": ["supersectional"], "-7.1 16.9 9.7": ["mineable"], "19.9 8.9 3.9": ["savants"], "11.8 -1.2 4.8": ["oohed"], "14.5 17.8 10.5": ["knifeman"], "-1.0 9.9 14.4": ["retrying"], "0.6 9.2 9.6": ["crankcase"], "2.1 4.7 2.5": ["septum"], "11.6 16.4 19.7": ["spinebuster"], "-3.4 17.5 10.3": ["moneyline"], "-3.1 2.9 34.3": ["cassoulet"], "9.3 9.2 13.4": ["lexapro"], "12.6 14.0 9.8": ["hehe"], "-4.6 7.2 0.8": ["redshift"], "4.8 12.2 17.4": ["riptide"], "-4.6 1.4 1.6": ["elearning"], "-5.2 -0.4 10.6": ["hypercholesterolemia"], "8.8 4.7 15.4": ["confectioners"], "5.4 6.4 12.5": ["snapback"], "0.1 12.7 9.7": ["metalcore"], "21.1 -4.3 4.0": ["megadeal"], "2.8 4.7 -1.3": ["audiocast"], "-2.5 4.5 7.3": ["talukas"], "20.5 3.1 14.6": ["glistens"], "8.3 12.7 2.9": ["worriers"], "-5.3 -0.8 8.1": ["vanpool"], "-1.7 -1.4 -3.5": ["paramedical"], "3.1 18.6 2.4": ["troublemaking"], "8.2 3.4 9.6": ["microscopically"], "3.6 4.2 16.8": ["pouched"], "1.5 12.1 11.2": ["hashtags"], "15.0 15.2 23.0": ["phish"], "19.6 16.6 3.9": ["astral"], "0.9 10.7 0.2": ["phototherapy"], "11.5 -0.9 19.8": ["liquorice"], "5.5 5.0 -4.3": ["operationalising"], "10.9 9.9 5.5": ["adman"], "5.2 9.4 4.9": ["oem"], "3.0 6.8 14.7": ["shebeen"], "2.9 5.8 4.5": ["seismographs"], "-3.9 5.3 2.6": ["nephrologists"], "10.3 -0.3 13.3": ["cabler"], "8.3 0.4 12.3": ["hyperkinetic"], "-1.8 8.3 5.7": ["codebase"], "5.6 0.1 5.4": ["watchmakers"], "10.1 5.7 9.1": ["celebutante"], "10.7 7.6 9.9": ["wingtips"], "33.3 2.0 13.8": ["hairball"], "6.7 -2.0 3.7": ["centralizers"], "15.2 12.7 9.8": ["wingtip"], "-6.2 13.3 5.2": ["topcoat"], "-9.9 8.6 6.8": ["backlist"], "17.4 -2.9 4.6": ["doh"], "5.2 -1.7 14.4": ["ching"], "10.3 1.8 12.1": ["faceplates"], "-2.7 2.2 5.3": ["reinspection"], "1.1 3.8 48.3": ["yellowfin"], "-2.1 11.9 13.4": ["leavening"], "1.0 0.0 0.2": ["sucess"], "3.5 18.7 -1.1": ["cybercrimes"], "2.1 16.8 17.2": ["caprice"], "1.2 2.6 12.5": ["lunchtimes"], "-5.1 -1.4 13.6": ["composts"], "8.5 -0.8 10.5": ["treacly"], "-1.0 17.8 2.3": ["unfaltering"], "0.1 6.0 10.4": ["tattooist"], "17.4 14.3 13.2": ["enticingly"], "2.6 18.0 4.2": ["accustom"], "7.4 11.4 1.4": ["lambasts", "benefic"], "6.5 7.0 13.2": ["stickball"], "6.5 -2.6 -3.0": ["hryvna"], "-1.2 14.5 10.5": ["trilogies"], "7.5 8.8 13.3": ["assed"], "-3.7 5.6 -0.8": ["disrobing"], "11.7 4.3 6.9": ["african"], "5.6 10.0 4.2": ["swigs"], "12.9 6.7 6.0": ["throbs"], "3.1 2.9 16.1": ["ppt"], "5.2 11.0 5.4": ["muezzin"], "7.9 8.6 15.9": ["slothful"], "16.7 6.1 3.8": ["magnifier"], "10.4 16.6 29.7": ["headlands"], "4.2 0.6 -3.7": ["leaseholds"], "-1.5 -1.1 -1.0": ["conveners"], "7.4 4.8 22.6": ["slicer"], "18.4 10.5 21.4": ["wildcats"], "3.2 24.1 12.7": ["flinches"], "-5.4 2.6 14.1": ["pickier"], "15.1 18.9 11.4": ["quivers"], "10.9 9.2 9.2": ["spams"], "2.9 13.1 6.2": ["northeasterly"], "16.8 10.6 15.7": ["jesters"], "8.9 15.1 10.0": ["fumigate"], "8.5 6.4 12.0": ["keening"], "18.0 5.9 0.9": ["baroness"], "-4.6 8.5 3.0": ["nuvi"], "-4.1 1.8 10.5": ["barbering"], "-2.1 0.3 4.8": ["undersupply"], "17.7 15.3 11.3": ["nether", "flickery"], "2.6 5.5 10.9": ["bellman"], "-1.9 4.8 6.3": ["snowpacked"], "0.2 -0.1 4.9": ["cosponsoring"], "-5.4 7.7 18.1": ["desilting"], "-5.3 7.2 10.5": ["carfilzomib"], "7.6 15.0 12.2": ["irredeemably"], "10.4 16.7 3.8": ["miscalculating"], "15.5 17.2 13.0": ["rube"], "13.2 12.8 15.1": ["grump"], "-4.4 6.0 10.3": ["polymerization"], "13.5 8.6 14.5": ["fecund"], "8.2 8.8 8.6": ["simpering"], "14.6 3.1 1.9": ["blinged"], "5.5 5.5 18.1": ["nam"], "8.5 14.1 19.7": ["obsidian"], "9.5 13.6 15.6": ["perchance"], "14.5 4.9 8.8": ["roughneck"], "1.1 14.8 3.4": ["persuadable"], "-1.9 8.2 -1.9": ["comprehends"], "7.5 4.2 11.0": ["singsong"], "13.0 10.4 10.5": ["overweening"], "3.1 9.3 5.6": ["terminologies"], "13.4 14.9 6.6": ["flacks"], "-8.2 13.6 -0.5": ["imputation"], "2.3 8.4 8.9": ["cabby"], "-7.3 2.3 2.3": ["flugelhorn"], "0.3 7.4 -1.1": ["reenergized"], "4.8 24.1 -0.9": ["sappers"], "0.1 12.4 -0.6": ["agaisnt"], "-5.4 4.2 4.0": ["elucidates"], "-1.4 -2.4 1.2": ["parabens"], "7.3 7.4 8.9": ["vanes"], "-0.0 7.9 12.5": ["dhoti"], "8.7 1.6 9.4": ["asa"], "3.6 11.4 15.1": ["indented"], "1.1 6.0 4.1": ["antiseptics"], "6.2 3.9 5.6": ["rewound"], "2.6 14.2 2.7": ["exhalation"], "14.6 16.3 4.7": ["zinging"], "14.0 10.5 20.1": ["stalactites"], "8.9 -3.3 0.7": ["bigmouthmedia"], "-3.3 6.0 0.7": ["prodrug"], "1.5 27.5 9.8": ["resupplying"], "1.6 -1.3 8.9": ["sts"], "12.8 1.1 4.1": ["employes"], "1.3 5.7 19.2": ["transpacific"], "5.4 18.6 16.0": ["neckbreaker"], "2.3 4.3 -1.2": ["postural"], "6.5 2.3 4.1": ["hungered"], "12.2 7.7 9.6": ["outlandishly"], "-4.0 2.8 13.3": ["freeride"], "-7.5 4.2 1.0": ["rhapsodic"], "3.7 9.8 -0.5": ["entrenches"], "4.1 13.1 3.6": ["gridders"], "-1.3 9.8 6.9": ["regifting"], "7.7 23.9 2.0": ["psychos"], "8.1 6.8 -4.4": ["withing"], "4.7 0.9 3.4": ["plz"], "4.0 8.4 3.4": ["intervenor"], "0.3 0.9 19.7": ["ruminant"], "0.6 5.0 15.8": ["jobseeker"], "-3.5 13.1 9.5": ["disinherited"], "1.1 2.5 4.2": ["recoupment"], "6.0 4.4 3.8": ["unworried"], "0.8 9.0 32.2": ["gratin"], "-0.3 4.5 15.1": ["partakes"], "14.4 20.3 20.4": ["raindrop"], "7.7 6.2 11.3": ["bleary"], "-8.6 11.2 4.1": ["distresses"], "19.3 20.6 15.5": ["monger"], "20.3 8.2 22.5": ["veined"], "7.4 8.1 15.9": ["trapezoid"], "0.7 7.5 7.0": ["invasiveness"], "-5.5 -1.4 7.3": ["hymen"], "14.3 10.5 17.5": ["antipodean"], "-2.0 10.6 18.0": ["pilsner"], "5.4 4.1 8.1": ["probers"], "7.7 10.3 26.3": ["sedum"], "-2.8 -0.9 -3.7": ["airpark"], "-3.4 11.3 7.3": ["forefoot"], "-7.6 19.9 3.5": ["interventionists"], "11.1 4.2 9.8": ["stroppy"], "12.6 0.8 3.3": ["jousted"], "-4.0 9.1 16.9": ["ripens"], "-2.9 3.7 11.3": ["ratable"], "-5.3 -1.0 4.8": ["colonias"], "1.5 2.4 3.1": ["hymnals"], "6.6 11.4 -2.7": ["purifier"], "17.5 -3.1 16.6": ["sayonara"], "3.6 7.0 9.6": ["handwork"], "-8.3 -4.6 5.0": ["vertebroplasty"], "2.2 12.8 6.0": ["landholder"], "-1.9 12.4 8.6": ["underexposed"], "9.3 8.3 4.6": ["clamorous"], "7.5 14.4 8.7": ["spatter"], "2.4 13.6 9.1": ["loosest"], "5.5 6.3 11.1": ["hob"], "1.9 7.9 0.6": ["footages"], "19.8 6.5 3.4": ["turnround"], "12.7 23.4 5.7": ["compadres"], "-5.2 15.3 3.9": ["wicking"], "2.1 5.0 7.0": ["chador"], "4.5 6.3 0.4": ["anointment"], "23.4 5.0 5.8": ["funhouse"], "-5.5 2.6 7.8": ["oblast"], "7.9 12.3 11.9": ["flowerbed"], "6.0 4.8 10.9": ["highrises"], "5.8 7.3 37.2": ["parsnip"], "0.9 4.8 12.1": ["winningly"], "2.7 3.1 6.9": ["ell"], "3.6 3.9 12.1": ["camshafts"], "6.2 11.5 14.7": ["quants"], "-7.8 1.8 6.3": ["digoxin"], "9.2 4.5 3.0": ["firebombings"], "2.6 8.3 -3.2": ["channelize"], "-2.1 11.9 0.8": ["depreciates"], "7.2 3.0 6.2": ["stockyard"], "9.0 5.5 16.5": ["hu"], "8.5 9.0 11.0": ["transtasman"], "10.8 5.0 18.4": ["downy"], "11.3 4.8 7.7": ["armload"], "-8.1 6.2 5.9": ["prostatectomy"], "7.1 6.2 0.2": ["overspill"], "9.2 11.6 26.9": ["woodpile"], "-1.4 8.6 12.8": ["parlays"], "10.3 3.6 8.5": ["hmmmm"], "-2.5 12.1 6.7": ["adrenal"], "13.9 7.5 7.2": ["catsuit"], "-2.4 0.7 6.0": ["radials"], "10.6 14.4 18.8": ["asp"], "2.8 8.6 20.1": ["flatbreads"], "0.8 20.1 11.7": ["craftiness"], "5.0 9.0 4.2": ["competiveness"], "1.4 15.6 14.9": ["turfs"], "11.5 7.2 8.9": ["ensnaring"], "-5.2 7.6 8.7": ["mycotoxins"], "6.7 1.1 13.2": ["loge"], "-1.2 9.7 8.8": ["certifiably"], "5.5 4.6 -1.6": ["paeans"], "-2.8 15.3 4.8": ["perspire"], "8.9 0.8 9.3": ["lunchrooms"], "-2.5 8.8 0.0": ["reengage"], "4.6 8.4 -0.9": ["obviates"], "18.4 23.7 8.9": ["forevermore"], "9.8 8.0 2.8": ["boringly"], "-1.4 15.0 21.2": ["retrievers"], "-10.6 1.8 -0.8": ["ratifications"], "0.0 12.6 16.3": ["submergence"], "14.9 34.4 13.6": ["destructible"], "4.9 2.2 1.6": ["reinvests"], "11.7 4.8 27.5": ["garter"], "2.2 8.6 10.0": ["clubgoers"], "5.5 16.5 14.1": ["overaggressive"], "-5.4 5.8 10.6": ["showrunners"], "8.8 3.0 15.2": ["cheesed"], "19.4 19.5 5.0": ["disemboweled"], "-8.6 11.7 6.0": ["redacting"], "-0.0 4.7 11.1": ["grindhouse"], "1.0 2.0 5.8": ["lector"], "9.6 6.9 18.1": ["macs"], "14.4 14.7 12.6": ["unhinge"], "-7.1 3.3 8.8": ["psychoses"], "-7.0 2.5 2.6": ["rebroadcasts"], "2.9 11.6 2.1": ["eradicates"], "6.7 18.0 6.0": ["kiloton"], "-0.6 13.3 6.6": ["peremptory"], "8.3 11.0 20.3": ["calcite"], "2.8 3.5 2.1": ["polypill"], "-7.1 -0.2 12.6": ["lifeguarding"], "0.6 6.8 13.0": ["closeouts"], "2.6 4.6 7.9": ["uninstalling"], "2.7 0.8 8.4": ["kvetching"], "14.0 7.8 6.3": ["snuffs"], "-5.1 15.9 2.7": ["abridge"], "7.7 3.5 24.4": ["floured"], "-5.3 -0.2 18.1": ["tanners"], "-7.7 8.1 26.8": ["renourishment"], "5.9 20.9 6.9": ["pointlessness", "atacked"], "0.3 2.4 2.9": ["spectroscopic"], "6.1 7.7 -0.8": ["lambastes"], "9.1 5.5 28.3": ["russet"], "-0.7 16.5 6.6": ["domesticate"], "-3.6 1.4 9.4": ["adductor"], "1.4 20.3 10.4": ["crotches"], "8.0 18.4 6.3": ["deadened"], "7.1 14.3 7.9": ["clich"], "13.2 7.0 22.7": ["boner"], "4.9 25.5 4.7": ["disunited"], "6.6 -1.7 16.1": ["pigtail"], "-1.4 22.2 -0.4": ["trustful"], "10.7 9.6 13.2": ["clifftop"], "9.3 6.2 8.8": ["undocked"], "0.5 4.9 9.1": ["overbridge"], "-0.2 14.7 1.0": ["romanticizing"], "4.3 2.6 13.7": ["celtic"], "14.0 14.8 10.7": ["kiddo"], "-1.8 7.7 8.2": ["tase"], "-11.4 5.0 4.7": ["upbringings"], "2.7 -1.4 12.3": ["embryology"], "10.7 -1.4 7.7": ["mucho"], "2.8 1.4 7.5": ["colonic"], "12.2 -5.2 2.2": ["reschedules"], "-1.8 4.4 13.7": ["nonrenewable"], "5.0 7.5 2.6": ["biotherapeutics"], "9.5 8.1 12.0": ["recombine"], "10.9 6.1 17.6": ["dockers"], "5.4 8.3 10.8": ["unmentionables"], "8.3 -2.1 0.9": ["recieves"], "-1.2 6.7 3.0": ["hypertrophy"], "1.3 12.8 4.8": ["redbox"], "8.4 5.1 3.5": ["backstreets"], "3.1 9.3 1.5": ["jewish"], "-0.5 3.8 5.1": ["waistbands"], "-8.3 3.8 9.0": ["coxed"], "-3.6 -3.2 6.5": ["provisos"], "10.9 10.3 23.6": ["hazel"], "-1.8 5.8 5.4": ["thrombus"], "12.7 19.4 16.1": ["cackles"], "3.0 1.4 3.6": ["layby"], "4.3 0.7 5.5": ["letterpress"], "4.0 10.5 45.6": ["alewives"], "-1.9 -0.8 7.3": ["preceeded"], "6.9 13.9 9.5": ["allegories"], "-0.1 29.0 2.4": ["proliferator"], "-1.5 4.6 2.5": ["turbodiesel"], "7.8 -0.8 4.9": ["holdall"], "5.1 10.8 5.1": ["thoroughgoing"], "-0.5 5.1 1.2": ["obviating"], "3.3 11.1 7.6": ["banalities"], "2.2 4.9 6.1": ["reframed"], "5.1 21.0 9.3": ["fightin"], "0.8 24.3 14.5": ["unlockables"], "3.0 6.2 4.0": ["lenience"], "6.4 10.7 4.2": ["prophesies"], "4.7 7.8 -3.4": ["undiscounted"], "-2.1 13.3 9.1": ["incompleteness"], "7.2 2.9 13.9": ["bunion"], "-5.7 21.9 4.6": ["briefers"], "3.0 14.3 4.4": ["satyagraha"], "-0.5 -3.0 -2.4": ["eurobond"], "14.4 16.8 14.8": ["impaling"], "-9.5 6.9 6.9": ["reappraisals"], "19.2 14.7 2.2": ["thunderclap"], "-0.2 12.4 3.4": ["salutations"], "3.6 9.9 26.5": ["hoagies"], "6.1 10.4 19.6": ["gaffs"], "1.6 1.4 7.6": ["hawed"], "23.8 9.8 3.1": ["boffin"], "2.9 7.4 10.6": ["coquettish"], "4.8 16.2 16.2": ["sinkerballer"], "-2.5 6.1 4.7": ["predisposing"], "-4.6 4.8 10.5": ["biopsied"], "9.8 11.6 27.0": ["periwinkle"], "13.8 11.3 30.0": ["hatchling"], "5.3 4.7 19.0": ["bullock"], "14.2 13.9 12.5": ["cackled"], "-9.6 4.3 12.7": ["malty"], "4.2 0.2 -1.2": ["claming"], "11.6 16.0 10.2": ["profiteer"], "13.5 6.8 12.3": ["tinkle"], "3.7 13.9 8.4": ["pusporte"], "6.2 16.4 8.0": ["joshing"], "9.7 23.9 12.4": ["obstinately"], "-0.7 0.2 10.8": ["malting"], "13.5 -4.9 1.9": ["shavers"], "3.7 -0.2 6.7": ["milliner"], "3.0 11.3 4.7": ["metes"], "4.8 11.9 8.3": ["fathomed"], "-4.8 8.9 21.6": ["drydocking"], "-9.4 1.5 2.5": ["anastrozole"], "-2.3 20.9 2.5": ["geopolitically"], "-3.0 2.0 2.6": ["supercedes"], "-12.7 6.9 13.5": ["ginners"], "9.3 8.3 9.8": ["galacticos"], "1.6 5.9 5.6": ["rebury"], "14.1 19.0 17.1": ["vampiric"], "1.7 16.0 0.7": ["outskirt"], "7.7 1.8 2.8": ["ethnography"], "-0.5 -1.7 5.0": ["impressionists"], "16.0 -1.2 14.7": ["bovines"], "14.5 16.0 6.6": ["unbidden"], "0.1 5.7 -4.4": ["eigth"], "15.1 5.3 0.0": ["aeronautic"], "3.2 2.8 4.0": ["titters"], "4.9 8.6 -1.8": ["schoolhouses"], "2.2 0.4 7.6": ["sed"], "10.8 8.7 11.7": ["goofballs"], "6.3 22.8 3.0": ["metastasizing"], "9.6 2.2 7.5": ["ottomans"], "-1.4 3.9 16.3": ["watercolorist"], "2.8 21.7 10.1": ["amour"], "4.9 4.0 9.6": ["autumns"], "10.2 3.4 11.0": ["fiesty"], "-1.9 6.6 7.2": ["reinstituting"], "0.9 7.7 10.7": ["parceling"], "1.0 8.1 0.4": ["fortwo"], "9.6 15.7 10.8": ["toff"], "1.1 5.3 9.9": ["babied"], "18.9 8.0 26.1": ["harpooned"], "0.2 20.8 17.8": ["riffle"], "-3.3 3.4 7.3": ["maraviroc"], "2.9 3.9 14.3": ["lithographic"], "8.3 2.5 15.7": ["sauropods"], "11.0 10.1 22.5": ["bruins"], "-9.6 5.6 6.1": ["medaling"], "7.8 11.4 5.4": ["borderland"], "5.1 5.3 5.4": ["discoms"], "-0.2 0.7 4.9": ["rehoused"], "3.8 -0.4 18.4": ["grained"], "-3.4 14.7 1.1": ["indictees"], "6.8 4.1 4.5": ["deux"], "21.3 11.8 6.3": ["nimbler"], "0.4 3.9 14.5": ["shoeing"], "16.1 -5.8 15.0": ["goosed"], "-3.3 7.6 15.8": ["goldsmiths"], "14.9 9.4 4.2": ["playstation"], "7.4 10.4 7.5": ["presenteeism"], "-5.3 5.8 5.4": ["allopurinol"], "-4.3 8.3 9.0": ["fidaxomicin"], "-6.9 15.3 -1.4": ["paras"], "-0.9 5.6 7.1": ["unenforced"], "13.4 14.3 12.0": ["pterosaurs"], "-7.3 14.1 2.0": ["cogently"], "12.7 3.9 13.3": ["barcoding"], "8.0 16.1 -0.7": ["modernizer"], "12.1 10.3 9.1": ["clunk"], "12.4 12.4 9.2": ["glimpsing"], "11.1 26.7 18.8": ["sorceress"], "4.9 7.7 6.8": ["neurobiologist"], "17.7 20.1 5.4": ["flunky"], "3.5 10.4 1.2": ["devotedly"], "9.9 11.1 3.1": ["demystified"], "5.4 8.6 10.0": ["millwright"], "-0.1 6.5 -6.6": ["disclaimed"], "4.5 5.4 1.6": ["subleasing"], "9.5 10.2 3.2": ["atrociously"], "12.9 19.8 10.4": ["fiendishly"], "-1.2 9.1 12.4": ["forwarders"], "0.3 8.1 0.9": ["heckles"], "7.5 -1.6 29.1": ["housemade"], "-3.6 4.6 7.2": ["rueing"], "4.7 12.7 25.7": ["hibachi"], "-4.6 -2.7 1.5": ["accomodations"], "6.5 5.8 1.2": ["undersold"], "4.1 8.2 9.9": ["ani"], "-0.1 8.0 15.0": ["distaff"], "5.4 2.8 25.3": ["vermilion"], "1.1 15.6 25.3": ["groundcover"], "4.9 9.5 16.8": ["cesspools"], "-0.7 14.2 13.8": ["plebes"], "17.4 14.1 13.3": ["updraft"], "10.9 1.6 2.1": ["willbe"], "2.2 12.0 1.5": ["excoriate"], "10.8 9.7 27.6": ["rowboats"], "8.0 20.8 5.1": ["displeasing"], "2.2 -0.4 7.5": ["vicars"], "1.0 6.5 10.1": ["bluesmen"], "9.4 11.4 11.9": ["buffalos"], "-3.8 10.2 36.6": ["sauger"], "-2.3 3.8 5.5": ["gurdwaras"], "14.4 11.0 17.1": ["honeypot"], "0.9 2.1 -1.4": ["milliwatts"], "10.8 9.8 14.1": ["steeples"], "-1.0 9.7 -3.0": ["whelming"], "10.4 11.3 13.0": ["woodcut"], "11.4 17.7 8.9": ["whitey"], "8.6 15.8 6.9": ["apparatchik"], "5.1 6.1 4.4": ["apoplexy"], "9.2 6.5 19.4": ["shi"], "7.2 13.5 6.5": ["remap"], "-5.8 13.2 51.2": ["blackfish"], "9.9 3.4 2.9": ["embroidering"], "3.1 10.8 0.5": ["scathingly"], "8.1 4.6 13.4": ["laze"], "1.2 4.5 3.8": ["shushed"], "-3.4 9.7 1.3": ["foci"], "8.5 11.7 -4.8": ["unreceptive"], "7.6 4.3 8.9": ["cringeworthy"], "1.1 12.0 -3.5": ["kgb"], "-4.4 4.9 5.8": ["nazims"], "16.4 8.8 23.4": ["jellybeans"], "10.8 11.9 29.0": ["stags"], "9.2 8.7 21.3": ["blarney"], "-0.7 4.8 10.4": ["ataxia"], "-1.0 1.3 4.2": ["tiffs"], "6.6 17.8 5.2": ["unforgettably"], "6.4 0.7 27.4": ["takeouts"], "4.3 4.9 9.5": ["taylor"], "9.6 19.1 7.9": ["dimwit"], "4.9 12.0 -1.9": ["combust"], "1.3 10.7 7.5": ["sussed"], "0.4 -0.7 2.5": ["silicones"], "-0.7 8.6 5.0": ["keepin"], "2.2 -1.5 -1.3": ["securitisations"], "-1.4 6.8 7.0": ["fluxes"], "-2.3 10.6 10.0": ["sourness"], "7.0 3.9 14.7": ["granulated"], "5.9 12.5 16.0": ["rascally"], "4.2 20.1 15.2": ["astern"], "-7.1 -5.1 10.2": ["cryopreservation"], "10.4 19.0 12.9": ["windbreak"], "9.0 14.6 9.6": ["idiosyncrasy"], "1.1 4.6 9.8": ["skycaps"], "0.6 9.5 4.6": ["specificities"], "-8.1 -2.1 -0.8": ["upgradeability"], "4.4 3.7 14.1": ["scenesters"], "-7.1 7.8 -0.7": ["recirculated"], "16.5 12.2 7.5": ["croaked"], "16.4 11.7 2.1": ["crapped"], "2.8 -0.1 2.2": ["teardowns"], "3.1 5.6 -4.4": ["harangues"], "1.0 -2.5 7.9": ["grandnephew"], "-4.9 3.3 5.7": ["contraflow"], "0.1 9.2 -1.8": ["inbounding"], "-1.0 6.8 10.4": ["deworming"], "2.1 2.9 5.8": ["vamping"], "11.9 18.1 1.6": ["reorienting"], "9.9 3.7 1.1": ["bandbox"], "5.1 11.6 8.6": ["guardhouse"], "8.8 13.7 12.7": ["hermits"], "3.5 21.6 5.4": ["toughie"], "-6.9 9.1 8.9": ["perplexes"], "10.4 8.8 9.8": ["uns"], "4.1 -2.1 7.5": ["terry"], "25.5 3.0 2.0": ["mfg"], "10.4 8.3 12.9": ["castor"], "13.6 10.9 9.8": ["heavenward"], "17.7 9.4 26.0": ["porker"], "-2.1 6.0 7.0": ["topicality"], "3.8 7.0 5.9": ["adam"], "16.3 22.3 4.8": ["musketeers"], "4.9 10.9 7.6": ["snigger"], "-1.6 10.8 6.6": ["buglers"], "6.8 12.3 9.0": ["squints"], "7.6 12.2 -0.0": ["travesties"], "7.7 3.4 35.1": ["herbed"], "0.3 11.6 -0.8": ["stricture"], "9.5 2.6 15.3": ["roundness"], "3.4 -1.7 2.9": ["prizewinner"], "1.8 5.9 12.8": ["ticketholder"], "0.7 7.2 7.4": ["throughball"], "5.8 9.5 11.9": ["placeholders"], "12.0 2.0 29.8": ["peppercorn"], "-0.5 6.7 5.6": ["concensus"], "9.7 12.2 1.2": ["sickbed"], "-9.9 7.5 -4.9": ["iterated"], "3.4 13.3 17.3": ["fecundity"], "2.7 -3.4 -1.8": ["satchels"], "5.8 4.8 9.3": ["overindulging", "comtemporary"], "-3.1 10.4 11.3": ["anodized"], "-0.1 1.6 12.4": ["latino"], "0.4 15.1 5.1": ["nahin"], "22.9 9.8 32.6": ["jello"], "21.2 2.5 -1.0": ["divests"], "1.3 5.0 14.9": ["demurrage"], "8.0 5.1 -0.2": ["jampacked"], "7.9 -2.4 4.7": ["handwringing"], "13.5 7.7 6.8": ["beatific"], "2.0 22.6 -0.4": ["harrying"], "5.3 5.4 7.7": ["whodunnit"], "12.1 6.8 -0.5": ["reinsure"], "-0.9 7.8 -0.9": ["evenhandedness"], "7.0 4.4 12.3": ["kip"], "11.2 16.1 5.8": ["pillory"], "-1.3 10.8 -0.4": ["approver"], "-4.5 8.9 2.5": ["hypothesizes"], "1.1 5.2 5.3": ["rosuvastatin"], "-0.9 11.8 9.5": ["vegetated"], "1.8 12.2 27.5": ["peregrines"], "-1.7 -0.7 3.3": ["defrock"], "9.6 7.7 19.2": ["tongued"], "2.1 29.9 11.9": ["isolationists"], "8.2 3.6 21.9": ["gelatine"], "1.4 11.9 -4.6": ["castigates"], "-1.8 24.8 6.6": ["intolerably"], "9.8 -4.1 8.2": ["piggybacks"], "2.4 4.4 8.3": ["stanozolol"], "13.3 15.0 7.5": ["genuflect"], "12.4 6.0 11.6": ["trapezoidal"], "-5.1 4.5 3.9": ["freelances"], "13.9 8.5 7.7": ["petaflops"], "-0.9 8.3 9.0": ["lineal"], "11.0 21.6 6.8": ["cannot"], "8.2 4.1 16.3": ["vulva"], "11.4 9.6 14.6": ["fairyland"], "3.5 16.0 0.2": ["unforgivably"], "6.1 7.4 6.1": ["subindexes"], "5.0 1.8 19.5": ["dropoffs"], "9.7 13.3 5.9": ["entreaty"], "-3.5 5.6 16.4": ["silted"], "26.4 12.5 12.6": ["minstrels"], "1.1 3.4 15.7": ["brewpubs"], "5.4 16.8 8.1": ["duffer"], "5.4 6.6 27.7": ["compote"], "-5.0 -6.9 -4.0": ["microgrammes"], "4.9 10.8 24.7": ["spp"], "-0.6 3.0 4.6": ["eurobonds"], "0.2 7.6 6.1": ["collieries"], "-13.4 4.2 0.4": ["workup"], "3.4 8.7 -0.4": ["scr"], "-3.2 17.7 -6.1": ["unreached"], "-0.9 2.5 11.3": ["iridium"], "17.6 21.3 4.5": ["lapdogs"], "14.3 20.7 0.7": ["patriotically"], "2.5 12.9 6.5": ["horrifies"], "2.4 -2.7 8.9": ["ces"], "0.9 12.7 3.7": ["mystify"], "-9.4 13.6 8.3": ["unbelted"], "-1.1 21.8 11.5": ["overthinking"], "-11.6 5.4 -4.3": ["adjunctive"], "12.5 -1.6 9.8": ["ecofriendly"], "12.8 17.0 11.0": ["cutlasses"], "-3.1 8.7 3.9": ["overallotments"], "11.7 11.8 30.4": ["coots"], "-2.2 2.3 1.2": ["expunging"], "6.9 2.3 12.6": ["jae"], "-1.5 0.6 -5.8": ["neuropsychiatric"], "-0.5 1.7 13.8": ["auburn"], "-2.1 6.4 5.8": ["executory"], "2.4 10.5 12.7": ["cabdrivers"], "7.3 7.2 1.8": ["quadriplegics"], "1.7 4.9 3.4": ["stenographers"], "1.7 0.4 17.2": ["bach"], "6.1 4.9 12.2": ["hankie"], "3.9 -0.1 1.8": ["debar"], "0.1 3.6 -0.2": ["disabused"], "-1.3 -3.1 2.0": ["postmarks"], "5.4 13.3 12.8": ["shopaholics"], "-1.4 10.4 9.0": ["forestation"], "7.6 3.5 15.8": ["breadline"], "14.1 6.4 11.9": ["pharming"], "4.5 4.5 14.7": ["regasification"], "5.7 7.6 8.4": ["floggings"], "0.9 4.6 8.7": ["poppycock"], "2.5 19.1 9.4": ["slaveholders"], "-4.0 2.4 0.6": ["videophones"], "3.5 21.8 8.8": ["faker"], "1.6 14.5 9.6": ["spectating"], "3.8 19.6 20.2": ["hummer"], "-3.2 3.6 3.8": ["dextromethorphan"], "1.8 19.1 11.5": ["numbs"], "0.0 10.7 10.5": ["freedmen"], "12.9 8.4 9.8": ["odorous"], "11.1 10.9 13.0": ["slobber"], "9.3 13.6 8.5": ["unappreciative"], "4.3 -0.2 3.1": ["vee"], "-4.0 9.6 8.8": ["nickelback"], "23.2 9.7 28.1": ["tapeworm"], "12.3 13.5 27.3": ["coon"], "14.7 6.5 21.5": ["marmots"], "8.4 7.7 18.3": ["sloughing"], "0.8 9.7 10.0": ["loutish"], "18.9 13.5 8.8": ["manically"], "-0.3 0.7 8.6": ["thumbprints"], "-3.5 3.7 10.6": ["wicketkeepers"], "-5.5 3.4 9.4": ["azithromycin"], "14.8 4.3 12.9": ["undigested"], "19.7 4.0 6.0": ["astro"], "8.5 1.7 29.8": ["phyllo"], "10.2 4.0 2.0": ["crowdsourced"], "-3.7 8.6 1.9": ["parented"], "8.8 12.0 -2.6": ["vaporizes"], "14.8 11.6 3.6": ["cruddy"], "0.5 -6.2 -2.2": ["biomethane"], "5.1 8.0 1.2": ["geographers"], "2.2 7.2 3.1": ["monocoque"], "14.1 12.7 5.5": ["incomprehensibly"], "-3.5 15.3 5.3": ["interjection"], "10.4 11.1 5.9": ["domiciles"], "1.7 11.7 2.3": ["cooly"], "6.3 9.9 5.6": ["theyve"], "2.5 13.1 -4.2": ["misfeasance"], "3.4 16.3 18.5": ["ethnics"], "6.9 8.7 -1.3": ["chancellorship"], "9.1 7.4 10.8": ["recirculating"], "0.3 6.8 12.1": ["humerus"], "5.1 6.0 25.1": ["microbrew"], "-1.0 -0.1 -1.5": ["coproduction"], "0.5 -2.5 2.3": ["demystifies"], "-6.8 -0.9 6.4": ["polymerupdate"], "5.2 14.8 7.1": ["interdependency"], "6.1 13.5 5.5": ["triviality"], "13.8 9.4 4.8": ["bullishly"], "0.5 10.0 7.9": ["unicameral"], "-4.1 3.6 4.6": ["remits"], "-9.0 8.7 14.7": ["cytarabine"], "3.4 6.1 2.2": ["bequeathing"], "3.3 16.3 3.5": ["agnosticism"], "-2.8 5.0 7.8": ["backstories"], "22.4 8.5 14.3": ["mangy"], "6.6 14.5 6.3": ["rawest"], "11.6 -1.4 19.2": ["plumper"], "1.3 10.2 7.8": ["solenoid"], "0.9 8.3 15.0": ["matriarchal"], "-6.4 6.6 18.3": ["vlog"], "6.4 4.1 11.6": ["heres"], "19.9 25.7 4.9": ["dominator"], "1.0 10.4 3.5": ["matchdays"], "6.6 3.9 2.5": ["adjoined"], "17.0 5.2 -0.3": ["innocuously"], "0.3 3.4 9.4": ["sutured"], "-10.4 6.3 -2.8": ["aftersales"], "16.7 9.4 1.7": ["deliverers"], "5.6 12.0 16.7": ["stogie"], "3.0 4.7 3.3": ["stopwatches"], "-10.8 -1.2 -3.6": ["misoprostol"], "-0.2 11.2 12.2": ["gunsmith"], "8.7 -0.2 14.0": ["firefox"], "4.9 6.0 18.0": ["shipowner"], "8.4 13.0 8.1": ["metamaterial"], "-6.5 9.6 15.2": ["rationalizes"], "5.1 22.0 19.4": ["thrips"], "5.0 2.1 12.2": ["gan"], "5.6 20.4 9.6": ["eyepiece"], "13.1 4.4 10.7": ["finmin"], "0.8 16.1 1.5": ["uncleared"], "19.7 8.1 11.1": ["eggheads"], "3.4 20.6 2.4": ["deluding"], "-3.0 7.9 4.3": ["guardedly"], "2.3 -1.7 11.9": ["singlets"], "4.4 8.5 22.4": ["snowdrops"], "13.1 -1.0 11.4": ["mortage"], "9.4 18.0 12.5": ["vainglorious"], "4.0 5.6 6.0": ["impeller"], "4.6 14.2 7.7": ["hindu"], "18.3 5.5 -0.5": ["ancillaries"], "12.9 1.1 1.7": ["pampers"], "-4.5 8.2 -1.4": ["biologicals"], "5.7 0.9 2.7": ["taht"], "0.3 2.3 4.8": ["tt"], "2.1 7.3 10.3": ["botches"], "0.3 2.9 -0.9": ["untimed"], "-4.3 5.2 5.5": ["onfield"], "4.5 6.6 17.4": ["refrigerating"], "6.7 4.2 18.3": ["sleighs"], "-2.9 24.0 9.1": ["crosser"], "-0.3 -0.8 13.0": ["slipcovers"], "11.1 1.3 20.0": ["chinchilla"], "19.4 6.0 3.3": ["implosions"], "12.2 1.5 -3.2": ["exisiting"], "10.7 13.0 13.7": ["cairn"], "7.8 5.6 14.2": ["prft"], "13.6 4.2 5.8": ["faddish"], "3.4 9.3 9.5": ["digicam"], "4.0 15.7 14.1": ["cheesiness"], "10.2 -1.2 6.7": ["dn"], "7.6 14.8 6.2": ["poseur"], "2.5 1.5 4.8": ["aps"], "-0.8 12.3 3.0": ["trys"], "9.8 1.9 11.9": ["johnson"], "9.0 12.2 1.2": ["smuggles"], "0.0 1.1 1.2": ["choirmaster"], "12.8 19.3 7.8": ["shitting"], "14.5 22.7 6.4": ["hypnotize"], "6.3 22.2 5.1": ["quagmires"], "11.5 16.9 10.1": ["schoolchild"], "7.9 10.4 15.6": ["nubs"], "2.0 32.9 5.7": ["garrisoned"], "-1.6 -7.2 9.0": ["tur"], "6.8 11.7 9.3": ["larrikin"], "10.0 -12.3 8.2": ["tarted"], "10.9 13.0 5.1": ["supplicant"], "8.6 9.6 3.1": ["hopscotched"], "5.3 0.6 4.8": ["deh"], "5.1 10.1 21.5": ["townies"], "-4.6 1.4 -6.8": ["guaranties"], "-3.9 8.0 13.7": ["amantadine"], "9.7 8.4 8.2": ["reincarnations"], "5.0 14.0 12.7": ["qualm"], "15.9 14.5 7.7": ["polygonal"], "-4.4 2.0 25.4": ["urad"], "-2.9 6.8 1.4": ["thrid"], "9.2 20.6 9.8": ["verily"], "4.7 8.0 41.0": ["snakeheads"], "1.8 19.1 7.7": ["undependable"], "-1.8 2.8 12.3": ["ossuary"], "15.0 12.6 13.8": ["jesus"], "10.6 7.6 7.7": ["cheerless"], "0.6 8.2 5.0": ["drily"], "-2.2 8.4 5.0": ["longballs"], "-2.1 15.5 0.9": ["actualized"], "11.8 4.1 10.4": ["pocketful"], "1.4 14.0 10.6": ["intone"], "-7.5 11.5 -2.2": ["acetaldehyde"], "15.9 -8.1 2.3": ["voor"], "-3.3 7.4 9.0": ["brines"], "7.0 27.2 8.0": ["authoritarians"], "3.8 2.6 7.4": ["cochairman"], "11.2 -2.2 7.7": ["za"], "14.5 -0.1 24.2": ["ladles"], "-1.3 4.1 16.2": ["grange"], "12.4 7.9 21.9": ["spatulas"], "9.2 11.6 25.2": ["fishin"], "-1.0 5.0 2.4": ["bedwetting"], "9.2 26.9 2.6": ["diabolic"], "1.8 6.1 6.0": ["rbeck"], "2.4 12.5 7.1": ["legitimization"], "6.9 4.0 4.6": ["nonworking"], "4.3 19.3 9.8": ["malarial"], "1.5 6.6 17.6": ["carotenoid"], "13.0 0.6 8.0": ["limbering"], "13.0 14.9 4.1": ["imperceptibly"], "-1.7 9.6 21.4": ["unseasoned"], "15.4 7.8 5.1": ["centimes"], "0.7 34.0 8.9": ["riflemen"], "12.3 7.5 15.1": ["wellheads"], "-7.2 8.5 2.4": ["deportee"], "12.6 15.3 21.2": ["crumpets"], "8.9 -3.6 5.1": ["defraying"], "-3.1 -2.5 14.7": ["mouthfeel"], "6.7 -0.4 15.7": ["wellbutrin"], "9.5 9.8 0.7": ["forcefulness"], "1.4 0.2 4.2": ["biosynthesis"], "9.4 26.7 3.8": ["vilest"], "5.3 5.2 14.2": ["bangin"], "-2.6 1.9 0.5": ["excipients"], "15.9 15.1 10.2": ["fakers"], "14.4 15.8 1.5": ["filthiest"], "-3.1 6.8 3.1": ["invigilators"], "1.2 8.8 14.6": ["carpoolers"], "19.0 1.9 10.2": ["frenzies"], "-3.3 5.3 5.9": ["abouts"], "5.4 2.4 2.5": ["shoutout"], "0.1 5.9 4.9": ["medulloblastoma", "rasagiline"], "16.8 9.6 3.4": ["brashly"], "2.4 9.5 -0.9": ["estoppel"], "12.6 16.3 19.6": ["druids"], "2.5 11.2 -0.4": ["disequilibrium"], "-2.7 5.9 -2.4": ["namaz"], "3.5 1.8 1.5": ["preform"], "1.3 4.3 1.5": ["fom"], "21.0 19.4 15.6": ["boomerangs"], "-10.7 -0.3 5.2": ["tacrolimus"], "8.2 1.5 8.2": ["shoeshine"], "16.2 7.5 10.0": ["longhorn"], "-3.4 2.5 12.3": ["thesps"], "14.4 28.0 10.5": ["citadels"], "-5.0 -3.4 17.3": ["updo"], "9.9 11.3 15.2": ["croaking"], "-1.6 4.0 4.6": ["mileposts"], "-6.0 5.8 4.5": ["nonsupport"], "6.9 15.1 16.0": ["windbreaks"], "3.2 4.4 16.7": ["antipoverty"], "10.8 6.5 8.1": ["licencees"], "0.5 15.3 8.2": ["transgressing"], "5.3 -4.4 7.5": ["scrutineering"], "7.1 -2.0 22.0": ["chung"], "1.2 8.4 6.6": ["prospected"], "5.7 -0.8 9.4": ["ruminated", "nontelevised"], "-0.1 3.3 5.1": ["cinematographic"], "9.5 5.1 10.1": ["sumptuously"], "32.5 10.6 7.5": ["elephantine"], "-13.4 11.2 4.9": ["intubated"], "6.3 4.3 18.9": ["premix"], "11.6 2.9 12.7": ["supercasino"], "1.1 4.3 14.8": ["veinlets"], "15.8 -0.1 18.4": ["canopied"], "10.6 12.4 4.9": ["bricking"], "13.2 4.6 6.1": ["singapore"], "14.4 16.7 37.5": ["carapace"], "-3.6 1.5 13.6": ["nonfat"], "5.1 4.1 7.3": ["decontrol"], "4.5 2.4 5.0": ["whittles"], "0.3 12.2 9.5": ["nearsightedness"], "8.0 11.2 17.7": ["corvettes"], "-3.2 2.7 23.3": ["trattoria"], "2.9 3.7 13.2": ["contralto"], "6.4 5.6 17.1": ["cession"], "12.7 10.6 17.9": ["teabag"], "9.1 9.6 18.5": ["pokie"], "15.4 8.2 9.9": ["lovelies"], "-3.3 11.7 -2.2": ["universalism"], "6.7 6.6 29.7": ["calzones"], "20.7 4.0 14.7": ["docklands"], "4.6 5.9 5.5": ["tollways"], "9.7 7.3 14.0": ["peevish"], "-4.4 10.2 15.6": ["conservancies"], "-3.6 1.3 7.9": ["collectibility"], "8.1 4.7 7.5": ["boosterism"], "-1.3 -0.5 -6.2": ["vouches"], "-8.4 10.0 6.6": ["misquoting"], "-0.9 0.9 3.0": ["healings"], "6.3 12.5 15.1": ["ozeki"], "-13.5 4.3 1.0": ["eduction"], "0.3 4.6 62.0": ["turbot"], "0.3 4.0 18.2": ["streambed"], "-0.8 5.9 1.8": ["printhead"], "-2.9 4.3 6.1": ["lapatinib"], "-3.9 -1.5 8.8": ["polyurethanes"], "-5.2 -3.5 5.3": ["nanograms"], "18.5 12.0 12.0": ["wallops"], "1.0 2.6 2.2": ["solvers"], "-3.6 1.6 5.3": ["kora"], "5.4 4.2 29.2": ["gooseberry"], "-0.1 12.5 3.3": ["definetly"], "6.9 20.8 2.1": ["intension"], "-8.0 8.5 7.6": ["actuals"], "8.4 6.5 7.6": ["powerpoint"], "0.1 8.8 25.1": ["floatplane"], "-2.4 10.6 1.0": ["acclimatising"], "2.0 -0.5 8.2": ["notecards"], "5.2 7.6 7.6": ["reforest"], "17.2 11.2 14.9": ["caped"], "-12.3 10.6 11.6": ["anhydrous"], "12.6 14.9 18.5": ["seaboard"], "16.2 4.1 14.1": ["quacking"], "10.7 4.3 12.6": ["landers"], "-0.3 16.5 31.9": ["huckleberry"], "12.6 19.0 15.7": ["hugger"], "9.6 6.6 4.9": ["grotty"], "9.0 4.0 12.5": ["unis"], "9.9 7.2 18.5": ["cyan"], "9.9 15.7 7.9": ["stabber"], "7.9 5.9 3.7": ["paroxysms"], "6.9 15.6 1.0": ["overdependence"], "-0.1 16.9 17.2": ["cheatgrass"], "11.7 9.3 18.4": ["gangplank"], "-1.7 13.8 5.8": ["grittiest"], "2.0 15.9 8.5": ["consigliere"], "14.7 34.1 8.6": ["hegemon"], "17.0 9.4 5.8": ["nitwits"], "-3.3 8.6 8.4": ["patriarchate"], "2.1 6.9 6.9": ["linker"], "1.4 14.1 23.0": ["lantana"], "6.4 15.1 13.6": ["slat"], "1.0 4.6 3.1": ["sexualised"], "-9.3 -8.9 10.9": ["formals"], "-0.3 13.3 5.7": ["jinxing"], "11.0 25.7 18.3": ["mercantilism"], "0.7 16.0 1.4": ["affronts"], "7.3 11.4 9.8": ["corkscrews"], "8.3 4.5 7.8": ["leer"], "-0.2 10.8 3.2": ["chargeability"], "3.9 -6.7 7.8": ["clerking"], "5.7 4.5 19.3": ["loveseat"], "-8.7 2.4 2.9": ["softswitches"], "1.8 12.9 4.5": ["correlative"], "2.0 6.4 5.3": ["antihypertensive"], "-1.8 1.3 14.2": ["anabolic"], "7.2 9.6 7.1": ["gearheads"], "-6.8 -3.1 -5.4": ["musicology"], "0.3 2.5 6.6": ["entombment"], "1.3 0.6 39.0": ["linguini"], "11.8 3.6 22.3": ["satiny"], "-2.8 23.7 5.5": ["airdrops"], "5.8 4.6 10.6": ["biennially"], "3.9 4.2 9.0": ["bmibaby"], "10.6 9.3 13.1": ["france"], "10.9 5.3 5.9": ["ooo"], "16.3 4.2 13.1": ["sizzler"], "2.0 3.7 10.8": ["pyrrhotite"], "4.3 0.1 -2.4": ["atrial"], "4.9 22.8 -1.3": ["unconventionally"], "1.3 1.6 -1.6": ["scribblings"], "7.0 3.2 9.6": ["wj"], "-3.5 -4.7 7.7": ["noncredit"], "7.6 21.6 11.0": ["braggart"], "1.8 10.3 10.9": ["screamo"], "-4.2 2.7 3.1": ["syllabuses"], "23.6 14.5 15.4": ["webbed"], "-2.4 -0.1 4.5": ["initialization"], "-2.0 16.7 1.5": ["surveilled"], "12.8 1.3 30.7": ["sable"], "5.6 5.8 9.2": ["vicarage"], "12.4 5.1 3.6": ["eyecatching"], "8.2 4.4 11.5": ["greentech"], "4.0 3.3 7.9": ["monomers"], "13.4 24.5 9.1": ["nuking"], "8.7 6.4 14.9": ["craig"], "6.5 3.7 7.1": ["geochemist"], "15.8 4.9 9.1": ["encases"], "0.9 11.2 11.1": ["borewell"], "1.2 8.8 26.7": ["braise"], "-11.1 7.4 3.7": ["recantation"], "7.1 4.9 2.7": ["slaved"], "1.8 23.7 9.1": ["resistence"], "-3.6 13.6 36.6": ["smallmouths"], "6.0 11.3 19.3": ["omnivores"], "-4.3 21.0 5.4": ["egoistic"], "4.3 7.3 15.0": ["foppish"], "-0.9 13.2 11.4": ["jodi"], "-0.3 12.5 9.8": ["uncultured"], "2.9 6.4 2.6": ["az"], "-5.1 6.6 5.8": ["proliferative"], "14.2 8.8 10.7": ["evanescent"], "-2.7 6.6 4.4": ["customizability"], "-1.4 20.6 2.0": ["texter"], "-4.1 4.4 17.7": ["fluoroquinolones"], "-3.3 12.7 -2.0": ["misprision"], "-9.6 8.9 19.5": ["woodlots"], "4.5 -5.2 7.8": ["primped"], "9.7 3.9 19.0": ["phat"], "25.9 8.8 9.9": ["unpronounceable"], "-4.8 -0.5 -1.4": ["documentations"], "7.6 26.2 15.8": ["minesweepers"], "-0.2 1.8 7.8": ["sirolimus"], "-9.4 -0.5 8.0": ["snowsports"], "10.1 7.5 8.4": ["occassionally"], "17.1 2.7 11.4": ["unwraps"], "2.1 13.7 24.3": ["fireboat"], "4.5 7.1 7.7": ["cardiomyocytes"], "0.6 40.7 1.1": ["unbeliever"], "-13.4 4.1 3.7": ["taxanes"], "-0.8 11.9 17.3": ["pith"], "5.8 15.6 8.8": ["shamelessness"], "-1.3 -4.5 7.6": ["pluggable"], "4.6 2.5 9.5": ["ber"], "10.5 10.4 14.3": ["whimpered"], "9.1 -0.2 7.9": ["timekeepers"], "-5.6 3.0 3.7": ["sermonizing"], "8.3 5.3 12.5": ["harmonicas"], "1.9 5.1 5.1": ["nettop"], "0.7 2.1 10.7": ["embalmer"], "4.6 -0.6 22.3": ["alders"], "3.3 7.7 18.1": ["snowshoers"], "2.8 5.2 10.3": ["perplex"], "12.7 -0.4 3.2": ["medico"], "20.3 5.1 11.3": ["portended"], "21.8 12.0 14.7": ["fatties"], "-4.0 4.6 10.0": ["influxes"], "-8.4 29.1 7.4": ["radioing"], "-2.4 2.6 13.9": ["sportswriting"], "2.5 6.0 6.3": ["cannabinoid"], "2.6 10.3 18.0": ["flyway"], "-3.6 22.4 4.3": ["overtopping"], "12.4 4.2 27.6": ["flapjacks"], "-5.6 12.5 -0.2": ["mischaracterize"], "8.1 15.5 12.7": ["manservant"], "8.1 16.5 7.5": ["putdown"], "6.1 1.8 18.7": ["churros"], "0.7 11.6 -1.4": ["expressively"], "10.7 1.5 17.4": ["halloween"], "5.4 5.7 8.7": ["syncopation"], "0.6 9.8 12.7": ["gulch"], "1.1 2.2 2.7": ["disallowance"], "6.5 13.0 9.6": ["serf"], "7.2 5.5 6.4": ["unpick"], "0.8 12.9 13.5": ["inventively"], "2.4 10.8 4.1": ["quietude"], "6.0 15.5 4.9": ["frictional"], "11.4 2.0 23.0": ["bbq"], "3.7 8.9 30.9": ["vermicelli"], "-1.1 5.4 0.4": ["tomboyish"], "9.3 14.5 1.2": ["extinguishes"], "8.2 -3.4 -0.9": ["ont"], "17.1 -0.9 10.0": ["jiggled"], "-4.5 -3.4 14.9": ["mixology"], "6.3 1.6 4.9": ["refurb"], "-2.8 17.9 3.6": ["declassifying"], "12.4 13.2 6.5": ["tingles"], "19.6 13.1 11.8": ["pickaxes"], "-2.5 6.5 8.3": ["golfs"], "-4.1 3.0 19.7": ["prosecco"], "-1.9 -4.8 5.7": ["vespers"], "0.8 2.7 -1.8": ["reappraise"], "-7.5 22.0 1.4": ["empathizing"], "3.6 4.4 8.4": ["newsreaders"], "-1.2 1.7 1.9": ["sitagliptin"], "11.3 8.7 5.1": ["godawful"], "-6.5 1.2 1.2": ["urologic"], "1.1 8.8 1.3": ["counterproposals"], "8.3 35.7 2.4": ["strafe"], "-5.9 8.8 5.7": ["journalistically"], "18.2 9.6 2.4": ["inanities"], "1.0 7.8 8.3": ["bhi"], "7.9 23.6 4.4": ["iniquities"], "-4.3 -0.3 27.6": ["sugaring"], "1.7 2.5 0.7": ["metallurgist"], "10.3 14.2 11.0": ["showoff"], "-8.0 7.5 11.0": ["songcraft"], "-1.3 -2.3 3.6": ["dextrose"], "0.4 3.6 -4.5": ["unsuitability"], "4.1 16.7 0.8": ["hardnosed"], "-1.0 6.7 12.4": ["souks"], "-4.9 2.0 4.8": ["episcopate"], "8.2 14.2 10.9": ["whimpers"], "10.3 13.2 5.2": ["formidably"], "5.7 12.2 1.6": ["daunt"], "2.7 17.6 8.3": ["nihilist"], "8.1 1.2 12.8": ["camphor"], "-3.3 9.3 8.2": ["federalize"], "8.6 0.0 6.6": ["lushly"], "12.2 15.5 11.6": ["shootin"], "3.9 17.4 10.1": ["bahu"], "10.1 11.2 5.4": ["transposing"], "-10.3 8.9 7.3": ["overtraining"], "7.2 3.9 15.9": ["krewes"], "4.4 5.8 20.1": ["charlie"], "25.8 14.8 43.8": ["squids"], "-5.2 9.2 6.2": ["xviii"], "2.8 15.5 7.8": ["inverts"], "11.7 11.6 12.8": ["blackspot"], "12.3 6.0 10.6": ["waterslides"], "-4.1 14.2 6.8": ["microenvironment"], "-2.6 7.2 9.2": ["novena"], "8.2 21.0 9.3": ["parries"], "11.6 -8.0 1.8": ["cbl"], "5.1 0.4 11.9": ["flyaway"], "0.7 5.3 -2.4": ["heptathlete"], "2.0 8.0 12.2": ["anticipations"], "12.3 1.5 1.0": ["minoring"], "0.7 2.7 29.7": ["florets"], "1.8 10.8 1.8": ["definitional"], "-6.4 7.3 13.4": ["undervotes"], "10.8 1.9 13.8": ["bacchanal"], "-0.7 9.3 10.3": ["vocoder"], "-4.9 9.7 -5.7": ["constitutive"], "3.5 4.1 8.9": ["maquiladoras"], "-10.3 5.3 -8.3": ["contactable"], "5.1 12.5 3.9": ["offensiveness"], "-3.1 1.7 10.8": ["thermography"], "-1.8 6.6 11.8": ["sintering"], "-1.9 18.7 10.6": ["emirs"], "2.6 12.5 12.1": ["kaizen"], "19.0 9.6 21.0": ["acacia"], "-3.7 4.0 11.0": ["capitation"], "-5.2 2.5 5.1": ["preneed"], "2.1 -0.3 4.0": ["proofreader"], "0.4 21.5 7.7": ["padre"], "5.7 6.2 -1.3": ["distributorships"], "-1.3 2.0 7.4": ["lugers"], "10.0 3.2 15.5": ["hardhat"], "-4.3 9.0 6.4": ["assesment"], "2.8 0.0 14.5": ["sisal"], "5.2 -2.4 3.7": ["excl"], "-7.5 3.6 10.1": ["bondsmen"], "7.2 9.3 6.9": ["painkilling"], "-1.5 23.5 6.6": ["dualism"], "15.5 3.7 22.0": ["topiaries"], "-6.0 10.1 20.0": ["tael"], "5.0 0.9 11.4": ["prebuilt"], "6.1 13.6 9.4": ["nanostructure"], "-2.9 14.3 10.1": ["partier"], "3.5 5.2 1.8": ["unhappiest"], "13.3 25.7 11.4": ["mecha"], "13.4 -4.3 6.8": ["kickstarting"], "0.9 2.1 4.9": ["investees"], "-3.5 7.2 10.0": ["cadenza"], "-3.2 13.2 9.0": ["proficiencies"], "8.8 11.1 -3.6": ["unshackle"], "0.4 5.2 5.6": ["borns"], "-0.9 1.6 1.7": ["interoperates"], "14.2 7.7 17.3": ["eyeballed"], "6.6 11.0 10.2": ["headbanging"], "9.7 5.2 14.2": ["sundeck"], "4.3 7.2 8.9": ["paralympic"], "3.4 6.7 9.6": ["alliterative"], "5.5 10.1 5.9": ["incoherently"], "0.3 7.9 5.0": ["nonpermanent"], "16.8 2.3 7.2": ["gantries"], "2.6 13.9 9.5": ["grandbaby"], "13.0 10.5 8.6": ["shimmies"], "15.4 14.9 6.1": ["simpletons"], "-1.5 6.1 21.6": ["abaca"], "2.5 4.8 11.4": ["laterite"], "1.2 5.2 11.1": ["unruliness"], "-6.9 11.1 4.7": ["novelistic"], "-12.9 4.0 -0.6": ["hematological"], "19.0 -0.6 6.3": ["slims"], "14.7 10.8 3.9": ["deformations"], "9.1 -0.3 6.3": ["wackier"], "2.8 4.9 23.2": ["drizzles"], "-0.4 6.1 0.6": ["southwesterly"], "5.4 -1.7 7.3": ["cheerier"], "-1.7 12.1 7.0": ["interline"], "3.0 -1.8 10.3": ["prizewinners", "snakecharmer"], "5.1 12.9 7.1": ["outrightly"], "-9.1 12.4 1.5": ["privileging"], "5.7 3.0 10.5": ["jobbed"], "9.5 19.6 1.6": ["faultlines"], "-1.3 10.7 5.1": ["protectiveness"], "-0.0 13.1 13.7": ["affectations"], "-2.4 14.2 10.2": ["rigidities"], "13.2 18.3 5.3": ["unconquered"], "0.4 12.4 3.6": ["denouncement"], "9.4 11.8 7.8": ["authorites"], "-5.0 13.2 2.3": ["contractionary"], "12.1 7.9 19.9": ["gastronomical"], "15.9 4.7 13.0": ["goateed"], "5.9 16.8 9.1": ["direst"], "6.8 -1.9 10.1": ["dawdled"], "7.6 10.3 10.9": ["passionless"], "-1.5 7.9 8.3": ["noseguard"], "11.9 0.6 7.2": ["dungarees"], "-9.5 8.5 12.6": ["follicular"], "10.1 2.1 6.6": ["bricklaying"], "6.6 10.8 7.6": ["shakiest"], "-8.9 3.2 8.1": ["bituminous"], "8.0 18.2 2.6": ["auras"], "0.5 4.0 10.8": ["bighas"], "4.5 10.4 4.9": ["monolines"], "0.4 -1.7 9.5": ["dahil"], "-3.0 20.4 4.2": ["unremittingly"], "16.3 7.6 11.5": ["cuties"], "8.0 2.6 5.7": ["cybercafes"], "3.3 14.5 3.7": ["infective"], "12.5 2.9 11.2": ["sweepstake"], "18.1 14.2 10.9": ["ellipse"], "7.7 1.6 5.5": ["sugarcoated"], "3.7 8.2 0.5": ["teletype"], "4.1 7.7 14.6": ["paleo"], "10.5 -5.1 3.0": ["spiff"], "12.4 -2.5 23.3": ["pralines"], "6.0 4.4 4.6": ["cubbies"], "7.8 11.3 38.2": ["muskrats"], "5.3 1.3 10.6": ["grouting"], "-2.5 29.8 0.6": ["jehad"], "16.4 0.8 15.7": ["chewable"], "-5.4 23.9 2.2": ["dishonors"], "11.6 10.8 3.2": ["sorriest"], "15.6 22.2 9.1": ["sheeple"], "-0.1 21.2 4.7": ["abets"], "12.8 6.6 6.5": ["puckish"], "13.9 10.6 36.1": ["mealworms"], "-3.9 4.2 -3.1": ["prescreening"], "-9.1 6.5 2.6": ["erythromycin"], "3.4 8.7 9.4": ["subclass"], "7.9 2.5 12.2": ["nametags"], "-8.1 11.0 13.4": ["senioritis"], "2.3 12.2 6.4": ["jleicester"], "9.0 14.3 17.2": ["enviros"], "14.5 10.8 8.3": ["biochemicals"], "9.0 6.0 8.6": ["quaintness"], "25.1 7.1 13.4": ["muppets"], "1.0 5.2 13.4": ["transhipment"], "11.9 -2.5 15.6": ["porky"], "12.6 4.0 6.0": ["unedifying"], "13.4 5.3 11.3": ["tubas"], "6.1 6.1 4.8": ["biochemists"], "-1.2 6.8 -2.9": ["lateraled"], "11.3 15.4 9.5": ["tartly"], "-1.6 -4.0 -0.1": ["reworded"], "7.4 14.7 27.7": ["mayflies"], "12.5 5.6 17.9": ["curdled"], "15.9 1.5 9.8": ["shopfront"], "-6.9 17.8 19.3": ["attackmen"], "10.2 13.3 13.8": ["postie"], "8.4 21.1 5.2": ["lawbreaker"], "7.0 12.8 8.7": ["creativeness"], "3.6 10.8 16.2": ["enchants"], "-7.6 12.0 4.5": ["indisciplined"], "7.3 3.3 7.0": ["volcanologists"], "8.6 13.7 15.9": ["jimmy"], "2.3 9.7 23.0": ["wiseguy"], "17.0 8.6 1.9": ["fetishism"], "-1.7 10.3 11.0": ["upslope"], "2.3 6.9 6.1": ["italicized"], "16.0 2.2 9.8": ["listlessness"], "0.7 2.8 8.7": ["biophysical"], "4.8 8.3 1.2": ["nonexistence"], "0.1 4.8 7.1": ["padayatra"], "14.7 -0.9 22.7": ["crossbreed"], "3.3 2.4 12.0": ["garters"], "7.5 18.3 5.2": ["sinews", "crucifying"], "6.5 2.6 -2.0": ["digitalisation"], "6.8 -2.0 11.4": ["pom"], "-8.9 6.7 9.0": ["reprioritize"], "0.3 4.9 4.8": ["conjugation"], "1.6 6.4 10.1": ["overstayers"], "3.5 -3.2 22.4": ["portioned"], "12.5 9.4 8.3": ["manacled"], "-2.8 9.6 11.0": ["sacristy"], "-1.8 2.6 0.0": ["donepezil"], "26.2 12.6 20.7": ["cobweb"], "17.9 8.7 41.1": ["puffin"], "0.7 6.6 0.5": ["psychoactive"], "-2.0 24.6 -0.5": ["manhunts"], "-0.4 4.0 4.2": ["blab"], "8.9 17.5 5.5": ["philistine"], "13.2 -0.0 11.8": ["streakers"], "-4.9 3.0 12.7": ["dowries"], "-7.7 7.1 6.6": ["wrestleback"], "16.7 6.0 12.1": ["deckchairs"], "14.8 5.0 1.6": ["loped"], "4.3 8.6 7.0": ["organelles"], "3.2 7.7 11.4": ["sophisticate"], "1.8 21.9 7.2": ["destructions"], "-6.3 8.2 2.4": ["purdah"], "9.3 9.6 4.9": ["dynamical"], "1.6 -3.3 0.9": ["syndications"], "12.2 10.0 12.0": ["distended"], "4.0 0.8 22.1": ["torte"], "1.3 3.8 6.0": ["ministrations"], "17.4 6.3 1.3": ["retools"], "0.8 9.2 5.7": ["contextualized"], "15.3 11.5 11.2": ["pollies"], "-3.6 11.9 2.8": ["overdoes"], "4.2 10.7 2.8": ["soley"], "5.4 -0.8 1.6": ["evp"], "7.9 15.1 7.0": ["truncheon"], "2.6 24.6 7.3": ["aggrandizement"], "27.0 23.2 21.7": ["arachnid"], "-8.4 7.5 3.6": ["autoantibodies"], "14.8 9.8 11.2": ["verizon"], "4.3 1.3 7.4": ["deets"], "5.3 0.2 3.6": ["inklings"], "17.1 11.2 12.7": ["yokels"], "11.9 11.2 18.7": ["folktale"], "12.1 1.7 19.1": ["kevin"], "15.7 0.3 17.0": ["crinkly"], "18.3 23.2 12.1": ["battlements"], "-1.0 13.9 5.1": ["reassertion"], "-0.2 12.2 12.9": ["crudeness"], "14.6 15.0 4.0": ["tinkerers"], "-8.5 4.1 7.6": ["teleplay"], "15.2 13.5 13.1": ["grail"], "-5.8 8.2 4.7": ["reemployment"], "1.0 2.9 32.9": ["jicama"], "2.4 2.0 2.0": ["varnishes"], "-5.1 15.8 12.6": ["oncogenes"], "-5.8 1.7 -7.5": ["felicitations"], "-4.8 2.9 8.3": ["modo"], "3.8 8.1 9.8": ["hoody", "inefficacy"], "1.3 1.4 11.1": ["haw"], "27.4 18.6 12.6": ["frigging"], "-6.7 13.0 2.3": ["renominate"], "4.7 22.4 4.2": ["siloviki"], "21.0 9.8 7.2": ["bough"], "19.9 12.9 9.5": ["levitation"], "14.6 14.8 12.9": ["pickax"], "15.5 6.2 16.4": ["grinch"], "9.4 1.9 6.9": ["snuggles"], "3.1 9.6 5.7": ["gallstone"], "13.1 8.7 19.7": ["basted"], "8.4 16.7 9.9": ["biplanes"], "-3.1 10.1 -3.3": ["dissociated"], "-3.3 15.8 8.4": ["mutinied"], "4.2 8.6 12.2": ["dears"], "-6.8 -4.4 -0.7": ["cb"], "-1.3 14.5 -2.2": ["highhandedness"], "4.8 7.2 12.8": ["hostelry"], "0.7 7.3 8.2": ["microdisplay"], "7.1 6.7 13.7": ["matriarchs"], "15.3 4.9 16.2": ["pac"], "6.3 7.4 13.5": ["havin"], "17.3 2.3 10.8": ["moonwalking"], "-1.1 2.0 1.3": ["photoshoots"], "-0.4 9.2 11.5": ["crit"], "19.0 10.6 13.0": ["munchkins"], "0.3 6.0 3.9": ["measurability"], "0.9 17.1 7.7": ["noninterference"], "8.5 14.4 13.3": ["woof"], "1.1 11.0 7.9": ["connive"], "12.1 16.2 6.0": ["gashing"], "-1.0 -2.3 2.2": ["readdress"], "-11.2 6.7 10.9": ["telavancin"], "-8.7 10.1 8.3": ["rephrased"], "10.8 6.4 4.2": ["outperformers"], "10.7 1.0 12.9": ["miscellany"], "4.0 3.7 4.7": ["insole"], "15.9 10.2 8.0": ["unsteadily"], "-1.2 -1.9 26.1": ["carnitas"], "-7.1 7.1 5.2": ["interspersing"], "5.2 1.8 10.4": ["margarines"], "6.3 10.3 9.0": ["gearhead"], "1.0 -0.3 25.3": ["semolina"], "3.6 -9.5 11.4": ["quibbled"], "5.7 10.3 53.4": ["flatfish"], "6.6 19.1 23.0": ["attractant"], "7.4 13.7 -0.1": ["underinvested"], "-6.3 -4.0 6.4": ["codirector"], "-3.6 -7.2 7.9": ["cosmetologists"], "12.4 5.7 9.2": ["pulped"], "-4.6 10.6 7.9": ["proteases"], "-3.7 12.8 32.3": ["overwintering"], "3.8 9.3 7.5": ["phoniness"], "-10.2 0.5 2.3": ["nightwear"], "-8.1 12.7 0.7": ["contestation"], "14.9 6.2 5.0": ["fetishists"], "-3.3 11.8 -0.3": ["xix"], "-1.2 10.1 12.7": ["melancholia"], "-3.6 4.5 5.1": ["tehsils"], "8.6 1.6 11.0": ["lipping"], "-1.9 8.1 8.1": ["preferreds"], "-5.8 2.3 8.3": ["sais"], "-8.3 -5.3 5.7": ["prolapse"], "7.3 -1.4 9.3": ["bookbuild"], "9.5 14.3 42.8": ["snakehead"], "1.7 11.8 8.0": ["scald"], "12.5 5.6 8.9": ["figural"], "2.1 1.6 7.2": ["schlocky"], "-2.0 15.0 -3.3": ["interchanging"], "0.8 18.1 14.3": ["careerists"], "2.8 7.3 4.2": ["photogrammetry"], "10.8 12.8 0.8": ["dolts"], "8.5 -3.4 11.5": ["pigging"], "1.7 10.5 -0.7": ["aiders"], "1.5 2.9 15.4": ["minerality"], "2.8 9.2 0.5": ["middleclass"], "1.4 25.5 15.1": ["ballcarriers"], "-1.8 13.9 13.0": ["intonations"], "0.6 1.1 2.8": ["whe"], "1.5 6.5 11.8": ["cassis"], "8.9 17.9 0.9": ["deafened"], "6.6 16.6 14.2": ["feminized"], "6.0 9.4 7.4": ["screechy"], "7.6 4.9 19.1": ["sai"], "28.7 23.3 7.6": ["hydra"], "12.3 9.5 20.3": ["squirmy"], "0.6 -6.1 4.4": ["rah"], "11.6 12.0 15.9": ["nutcrackers"], "4.0 -0.6 8.8": ["chocked"], "0.1 4.6 -0.6": ["preoccupying"], "-3.2 0.2 16.6": ["merino"], "5.3 17.5 1.1": ["alway"], "0.5 6.5 19.0": ["bantams"], "-0.9 10.1 7.6": ["reunifying"], "6.2 7.4 9.6": ["rampantly"], "14.5 9.8 9.4": ["televisual"], "5.8 13.1 4.1": ["perceptibly"], "-1.6 2.4 6.1": ["naptime"], "4.1 5.5 8.7": ["cud"], "6.1 1.3 9.9": ["onesie"], "-12.4 18.1 10.7": ["termers"], "1.0 3.5 2.2": ["misspell"], "13.4 -1.8 -0.3": ["annuls"], "-0.8 8.7 4.6": ["monolingual"], "4.3 0.6 32.8": ["satay"], "11.0 7.0 8.0": ["trax"], "4.9 5.6 4.1": ["dilapidation"], "-1.1 5.7 3.4": ["majlis"], "3.5 1.5 14.1": ["shim"], "13.0 10.5 4.3": ["absorbers"], "8.1 14.1 8.9": ["raucously"], "15.6 4.5 8.9": ["rejiggered"], "-2.0 17.4 0.2": ["counterargument"], "4.7 13.2 13.7": ["capsizes"], "-2.8 7.0 8.2": ["kettlebell"], "-1.7 4.8 13.4": ["weekenders"], "5.8 9.5 16.9": ["incisors"], "0.4 8.4 35.0": ["chumming"], "10.6 -2.5 5.7": ["finagling"], "3.1 2.4 8.2": ["bolus"], "-1.5 -4.4 17.2": ["pullovers"], "0.7 7.1 10.9": ["elesclomol"], "-0.7 -0.3 4.6": ["interregional"], "2.4 -0.6 8.0": ["maquiladora"], "0.2 10.4 -0.9": ["whitewashes"], "9.8 10.8 16.0": ["argot"], "19.4 19.6 24.5": ["wench"], "17.2 3.9 2.5": ["staplers"], "-3.2 -0.6 1.4": ["corr"], "7.8 16.2 13.3": ["protozoa"], "8.5 6.6 6.1": ["turners"], "5.4 1.2 6.7": ["biobutanol"], "-4.4 2.8 7.5": ["plyometrics"], "4.3 2.7 3.3": ["gigabits"], "-0.4 11.6 8.4": ["midtable"], "-0.7 11.3 12.7": ["underarms"], "-4.5 6.6 6.4": ["webcomic"], "3.4 8.4 16.0": ["limpid"], "7.2 -2.1 19.7": ["bluestone"], "7.8 6.7 54.8": ["bivalves"], "10.8 8.1 14.2": ["witchy"], "9.9 2.6 6.7": ["entrepreneurism"], "2.8 -6.3 12.7": ["cts"], "5.5 17.6 1.3": ["obstreperous"], "1.2 18.6 -1.5": ["unserviceable"], "-0.4 -2.7 13.1": ["millinery"], "0.2 0.6 8.6": ["shampooing"], "14.5 4.8 4.2": ["liveried"], "13.0 9.1 6.3": ["secretes", "navaratna"], "20.4 16.1 17.1": ["wombat"], "-3.4 8.8 3.9": ["flareup"], "-6.9 -1.7 -3.5": ["osteopathic"], "0.8 18.0 8.7": ["emasculation"], "3.9 6.5 9.5": ["evenness"], "-6.5 5.1 11.1": ["fruitiness"], "11.8 14.5 20.6": ["arboreal"], "9.2 4.5 8.8": ["jauntily"], "0.8 0.2 19.8": ["kayaked"], "-5.9 1.4 10.2": ["countertenor"], "-0.8 -1.7 5.0": ["camogie"], "-10.6 16.4 6.8": ["irregardless"], "4.0 4.7 12.4": ["reedy"], "0.1 7.4 5.0": ["secretariats"], "6.4 10.4 6.3": ["enervating"], "-5.2 2.6 11.1": ["tokenization"], "-2.9 6.5 4.1": ["tivozanib"], "10.6 3.6 12.1": ["funkiest"], "8.8 15.3 7.7": ["morbidly"], "-4.4 10.9 7.8": ["acyclovir"], "2.5 -5.4 9.0": ["bioprocessing"], "15.5 14.8 6.1": ["wallflowers"], "5.3 5.3 8.4": ["noirish"], "-0.3 13.3 5.6": ["marginalizes"], "1.1 4.0 9.1": ["bookbag"], "4.2 6.7 29.5": ["ferryboat"], "3.9 2.8 15.6": ["eaterie"], "4.5 5.8 20.6": ["chocolatey"], "10.5 7.9 8.2": ["grifter"], "15.3 4.8 5.6": ["rollerblades"], "0.1 6.3 12.1": ["rakhi"], "4.4 5.6 2.8": ["shoddily"], "-1.1 41.8 16.4": ["respawn"], "-1.5 2.6 5.7": ["biogenerics"], "-5.1 10.6 6.8": ["retreatment"], "13.1 9.7 7.7": ["trilling"], "-2.3 -0.9 13.6": ["broadway"], "3.4 -1.1 20.1": ["creamier"], "7.7 8.7 2.8": ["cybercafe"], "8.6 9.3 2.0": ["consumerization", "magzine"], "18.3 16.9 20.6": ["kestrel"], "1.4 10.3 14.7": ["breakbeat"], "12.9 13.6 12.2": ["dervish"], "-4.6 9.2 4.4": ["resend"], "0.7 4.2 6.3": ["hvy"], "-2.2 6.2 5.2": ["streetball"], "0.5 4.0 4.7": ["socalled"], "-1.0 17.2 21.2": ["triads"], "12.2 22.1 26.9": ["woodchuck"], "12.0 9.6 18.4": ["crinkle"], "-2.0 11.8 15.1": ["denuclearizing"], "-4.6 20.6 5.9": ["respecter"], "11.3 5.2 12.6": ["prismatic"], "-4.1 6.7 6.9": ["scapula"], "2.9 2.7 7.1": ["rumen"], "-8.3 7.0 2.8": ["unprofessionalism"], "19.9 6.4 15.6": ["turds"], "-2.9 11.3 6.1": ["infectivity"], "-0.6 16.3 0.2": ["misreads"], "6.1 17.7 6.3": ["nutjob"], "1.9 6.8 5.5": ["postmasters"], "-12.0 -7.4 -0.3": ["workshopped"], "9.4 13.5 12.8": ["treater"], "3.7 4.5 9.9": ["nacelles"], "3.8 -0.4 13.0": ["repacked"], "9.3 20.6 10.6": ["standers"], "14.5 -2.2 -1.5": ["boogied"], "-13.2 0.8 1.6": ["yeshivas"], "4.9 1.4 19.3": ["fayre"], "-7.1 11.5 12.4": ["backfilled"], "-10.3 3.5 0.2": ["loungewear"], "-0.2 6.2 6.5": ["acapella"], "5.8 10.4 6.2": ["fastidiously"], "-4.1 4.3 6.1": ["retinol"], "1.2 6.0 2.4": ["tipline"], "4.4 13.2 11.2": ["prognosticating"], "-0.7 10.3 7.2": ["retreading"], "-4.1 6.4 1.8": ["retrials"], "6.2 5.7 9.2": ["chem"], "17.9 19.1 9.0": ["bipedal"], "6.2 11.2 3.7": ["artless"], "3.0 11.6 14.1": ["obliviousness"], "14.0 0.2 -0.5": ["wallpapered"], "20.4 18.1 13.0": ["bloodsucking"], "1.9 6.4 5.3": ["overproduce", "ntoskrnl"], "7.2 14.2 20.1": ["conkers"], "4.3 11.2 10.5": ["hedonist"], "5.5 3.8 1.7": ["faultlessly"], "6.2 10.9 5.7": ["cosmologists"], "9.5 5.4 21.4": ["icecream"], "8.1 3.7 7.9": ["xmas"], "5.2 0.4 13.8": ["jackson"], "-9.1 6.1 8.7": ["ispinesib"], "26.4 1.8 5.4": ["flatulent"], "-1.9 2.1 1.5": ["anguishing"], "14.1 0.3 0.0": ["thatthe"], "-1.1 11.6 7.9": ["funks"], "13.2 5.2 7.9": ["messiest"], "3.1 14.3 12.4": ["rhinovirus"], "6.6 8.2 44.8": ["dugong"], "-2.2 6.2 0.4": ["indicia"], "-2.0 5.2 4.8": ["prolactin"], "25.2 18.4 3.1": ["monopolists"], "10.7 13.8 0.7": ["succesfully"], "5.8 13.1 26.2": ["bamboos"], "6.3 5.3 -3.9": ["reabsorbed"], "5.8 8.0 6.7": ["variably"], "-7.9 3.4 8.2": ["childrearing"], "2.6 1.0 4.7": ["presold"], "-10.1 -0.9 11.3": ["formalwear"], "17.1 6.5 17.2": ["cockerel"], "-0.3 3.5 12.0": ["oligonucleotides"], "-4.4 5.0 5.9": ["callus"], "-1.0 0.7 7.4": ["washcloths"], "22.6 6.6 13.0": ["hunchback"], "11.9 7.7 16.6": ["chipmaking"], "11.8 14.6 13.0": ["updrafts"], "20.3 0.6 13.9": ["multitiered"], "2.3 6.5 3.7": ["betwen"], "7.2 -3.1 5.8": ["rubbernecking"], "1.0 7.5 4.8": ["unmerited"], "5.8 -6.5 9.1": ["houndstooth"], "-4.8 12.0 51.0": ["weakfish"], "7.4 1.5 8.7": ["bur"], "1.4 1.4 11.6": ["ubiquitin"], "-2.9 -6.4 12.5": ["biannually"], "-3.7 -1.7 0.0": ["phlebotomy"], "7.8 19.1 7.5": ["misdirect"], "-3.5 9.5 9.3": ["farmsteads"], "4.7 0.8 2.3": ["underbid"], "2.5 9.1 10.3": ["hearths"], "5.4 18.5 10.5": ["crueler"], "10.9 18.0 16.3": ["crags"], "-9.1 -1.2 13.1": ["dressier"], "0.5 4.6 11.0": ["jibed"], "14.4 14.6 11.7": ["beneficence"], "3.5 4.4 11.3": ["meetinghouse"], "8.4 9.2 12.0": ["vertex"], "-0.3 21.3 -0.7": ["subordinating"], "9.1 9.5 8.0": ["franchisers"], "2.4 2.5 -0.2": ["donators"], "1.3 11.8 6.4": ["vestibular"], "-5.3 2.5 5.1": ["boed"], "-1.3 7.3 25.7": ["ciabatta"], "4.9 6.3 7.0": ["dispensations"], "-3.8 6.3 8.1": ["regionalizing"], "10.9 19.9 14.3": ["ramrod"], "1.3 6.7 9.7": ["enterovirus"], "-3.0 9.1 2.5": ["subtractions"], "1.2 6.0 9.7": ["recut"], "1.9 2.6 -0.7": ["galled"], "0.5 32.2 22.4": ["shipmate"], "-5.0 10.0 8.0": ["adits"], "15.3 3.6 11.3": ["hayfever"], "7.1 13.1 6.6": ["unsalvageable"], "7.1 13.9 8.6": ["imponderables"], "2.2 14.5 6.6": ["outriders"], "3.8 -2.1 5.3": ["catchier"], "7.6 6.0 5.9": ["reconfirmation"], "-5.0 9.9 5.7": ["cohere"], "2.0 15.3 4.5": ["provincialism"], "-1.2 3.1 7.0": ["repack"], "3.2 6.4 19.4": ["grumpiness"], "0.9 19.5 8.1": ["permethrin"], "2.6 6.7 4.4": ["overhit"], "7.0 -6.9 4.3": ["kuh"], "14.5 16.3 7.5": ["potentate"], "23.2 7.4 2.6": ["gazillions"], "15.9 2.7 11.6": ["beaut"], "-15.4 -1.3 4.7": ["accompanists"], "7.9 7.7 12.9": ["bbc"], "14.9 10.4 26.5": ["mounded"], "8.3 4.3 11.6": ["travertine"], "-1.0 3.3 4.7": ["radiologic"], "-1.8 4.6 3.3": ["constrictions"], "1.8 10.3 8.2": ["separable"], "20.5 11.9 24.4": ["weathervane"], "-0.3 7.6 4.1": ["synfuel"], "-4.7 -6.6 4.1": ["plasticizers"], "11.1 6.7 8.2": ["unmarketable"], "-5.2 -4.2 14.7": ["weanlings"], "10.4 8.8 8.9": ["africa"], "-4.0 7.9 8.6": ["backflow"], "-2.1 6.1 8.0": ["codex"], "1.7 4.6 15.2": ["spearmint"], "9.8 5.7 9.4": ["clearout"], "9.3 17.6 11.0": ["zig"], "-4.0 6.4 8.2": ["twosomes"], "19.3 4.7 2.8": ["ization"], "11.6 8.3 5.6": ["boisterously"], "12.2 11.5 9.1": ["supplicants"], "-6.4 6.7 5.4": ["dp"], "0.1 7.9 0.8": ["restaging"], "1.9 6.5 9.3": ["hah"], "3.7 17.2 8.8": ["misanthrope"], "10.0 6.7 11.2": ["fullerenes"], "-6.9 2.9 1.9": ["gpm"], "-7.0 15.6 3.2": ["triaged"], "9.8 8.2 7.7": ["bitchin"], "12.9 -1.0 12.7": ["fied"], "5.4 14.2 6.0": ["signifier"], "-5.1 5.0 6.5": ["dieted"], "7.5 14.1 15.3": ["clotheslined"], "-14.3 7.1 0.6": ["presentence"], "13.5 1.7 14.2": ["bloatware"], "-2.7 1.7 -4.8": ["outstandings"], "-2.2 5.4 7.0": ["transpiration"], "3.7 5.3 4.3": ["bedpost"], "5.2 12.1 10.5": ["synchrony"], "3.5 6.2 8.7": ["fannies"], "-6.3 7.8 1.3": ["eloping"], "8.1 2.8 4.7": ["cyclotron"], "-8.6 10.4 1.7": ["apostolate"], "0.8 24.0 0.9": ["civvies"], "8.6 2.3 9.9": ["microcomputer"], "5.7 1.1 1.8": ["computerizing"], "-0.6 15.5 2.5": ["theoretician"], "0.3 0.7 0.4": ["disinvited"], "3.4 19.6 6.4": ["nightsticks"], "5.3 1.2 16.9": ["kaya"], "6.4 -1.0 3.1": ["antifraud"], "12.7 9.7 3.8": ["myriads"], "6.8 0.3 21.6": ["nang"], "21.0 11.4 18.5": ["tosser"], "2.0 10.4 11.3": ["firebox"], "13.8 14.0 24.5": ["foghorn"], "10.2 4.3 7.6": ["bien"], "5.7 9.7 21.5": ["sandbank"], "-3.3 3.2 11.1": ["photomasks"], "6.0 2.3 17.7": ["dreamboat"], "1.3 3.7 0.4": ["carcinogenesis"], "-6.1 12.4 16.5": ["tremolo"], "0.4 3.8 21.9": ["smokiness"], "10.0 17.6 0.2": ["ennobled"], "10.5 7.0 28.1": ["corgi"], "8.7 13.0 19.6": ["hawthorn"], "7.3 -2.0 8.7": ["pubcaster"], "-0.8 5.3 12.8": ["nonagricultural"], "14.8 5.9 8.3": ["unprepossessing"], "1.0 6.7 5.2": ["josh"], "-0.9 1.0 6.9": ["mudflows"], "9.7 6.7 6.7": ["unforseen"], "2.2 11.4 9.6": ["basepath"], "5.1 7.2 12.3": ["drawls"], "4.4 -1.8 8.8": ["clouted"], "2.3 3.1 11.7": ["repacking"], "7.7 6.2 2.2": ["basketballers"], "-3.3 -3.4 2.7": ["submittals"], "0.2 5.2 7.7": ["laquinimod"], "4.8 5.3 -2.2": ["losingest"], "14.0 6.9 8.8": ["sheeted"], "10.2 -5.9 8.2": ["bioproducts"], "5.8 1.5 3.1": ["contactors"], "5.7 9.7 0.9": ["vaguest"], "2.9 0.8 13.6": ["delicatessens"], "6.0 1.8 7.9": ["wll"], "-8.0 5.1 14.5": ["revegetation"], "-6.2 9.7 1.9": ["barracked"], "-3.1 10.9 -0.2": ["psychoanalytic"], "7.6 -6.6 -2.5": ["advertorials"], "2.7 7.3 9.5": ["saxagliptin"], "13.1 5.8 10.3": ["mustached"], "-3.6 4.5 0.6": ["harmonically"], "-6.2 1.4 1.0": ["gasohol"], "8.1 6.0 27.4": ["quiches"], "6.8 -1.3 9.3": ["backstreet"], "9.1 6.0 11.0": ["superrich"], "1.7 -0.3 2.7": ["abstracting"], "-3.8 22.6 6.4": ["interdicting"], "-10.5 4.0 4.5": ["poetess"], "0.0 5.9 5.1": ["counterpoints"], "7.2 5.0 1.1": ["shacked"], "16.3 10.6 0.3": ["mockups"], "9.4 12.7 10.2": ["bier"], "1.9 0.8 16.0": ["trestles"], "9.9 9.1 7.8": ["circumnavigated"], "3.3 5.8 1.8": ["dependance"], "15.7 0.3 9.4": ["zoologists"], "11.2 21.1 18.2": ["nunchuk"], "1.1 11.5 10.5": ["barkeep"], "1.9 7.1 15.8": ["pashmina"], "3.6 5.9 -0.5": ["lawyered"], "-1.9 7.5 22.5": ["orchardists"], "15.4 14.0 5.4": ["slumlord"], "6.2 1.8 30.4": ["nectarine"], "2.4 13.4 42.7": ["plover"], "15.4 14.8 22.8": ["flightless"], "6.7 -6.6 3.4": ["curatorship"], "-7.8 6.3 0.5": ["recollecting"], "-1.6 -3.1 6.9": ["paycut"], "-6.1 13.0 18.2": ["rootstock"], "-1.2 -3.3 4.4": ["blotters"], "6.2 21.3 12.3": ["fogs"], "12.1 11.9 9.3": ["incompetently"], "11.7 27.5 5.6": ["principalities"], "6.8 3.7 -1.4": ["intially"], "-1.6 0.0 23.5": ["lefse"], "3.9 14.3 10.8": ["boer"], "-5.4 1.0 10.7": ["baritones"], "1.2 10.1 5.1": ["overtax"], "5.2 12.3 11.2": ["quaff"], "10.9 7.1 8.7": ["illusionists"], "2.0 8.8 12.8": ["tude"], "12.7 2.2 6.3": ["och"], "2.4 13.5 4.8": ["represses"], "-1.8 9.9 13.1": ["remainders"], "-1.4 9.6 15.4": ["naturalize"], "13.6 -4.1 9.1": ["armfuls"], "9.7 8.1 18.6": ["decennial"], "13.0 6.5 7.4": ["demutualized"], "14.0 11.0 -1.8": ["arbitrageurs"], "6.5 2.9 -1.8": ["videolink"], "-3.8 3.9 0.8": ["phlebotomist"], "-1.3 4.8 14.8": ["stirrup"], "7.8 15.9 13.5": ["targetman"], "-4.2 0.0 1.7": ["prem"], "-2.2 12.9 9.2": ["leaners"], "27.3 16.9 16.1": ["armless"], "1.0 6.5 1.8": ["warrantholders"], "-5.0 4.5 6.0": ["ferreted"], "10.1 -0.8 10.2": ["certifier"], "19.5 8.3 18.8": ["footlong"], "13.2 15.6 8.4": ["amorality"], "0.5 12.1 1.7": ["conductance"], "10.7 13.6 5.4": ["riddling"], "4.9 31.4 9.9": ["emplacement"], "-4.4 15.6 16.7": ["understory"], "20.5 14.7 28.1": ["willy"], "-4.3 11.2 7.9": ["temozolomide"], "1.9 10.2 13.0": ["freestyling", "circumciser"], "4.4 -5.8 0.3": ["traineeship"], "9.4 18.4 7.4": ["exults"], "6.7 17.7 2.9": ["shareowner"], "10.2 16.0 16.9": ["flails"], "7.4 6.6 10.4": ["boggled"], "5.3 11.2 10.0": ["superfight"], "2.0 12.3 18.4": ["steeps"], "6.9 20.4 3.2": ["abducts"], "7.7 12.5 12.9": ["carpetbaggers"], "7.6 -2.2 8.2": ["longhorns"], "8.3 7.4 11.1": ["candybar"], "0.5 13.4 5.9": ["theoreticians"], "7.0 16.4 27.0": ["panga"], "0.5 4.7 6.6": ["renderer"], "-3.4 7.5 11.9": ["showery"], "4.5 0.6 16.3": ["togas"], "0.0 11.6 5.9": ["arteriosclerosis"], "-2.1 14.0 13.0": ["tincture"], "-6.4 0.8 7.3": ["daywear"], "-3.4 4.1 -0.7": ["acquainting"], "0.4 6.1 1.1": ["rhenium"], "11.2 1.8 12.9": ["wigged"], "1.6 9.8 1.9": ["accuracies"], "10.7 13.8 17.9": ["grazers"], "5.5 -2.1 19.0": ["topsides"], "5.2 4.0 17.9": ["jeff"], "8.0 7.0 11.6": ["eukaryotes"], "1.3 1.2 -7.4": ["biller"], "4.8 12.4 5.5": ["cubism"], "8.6 9.1 13.7": ["urinates"], "-3.3 -9.5 4.4": ["unpersuaded"], "13.3 0.2 -1.6": ["filched"], "2.0 17.6 3.2": ["crushingly"], "-9.9 5.8 1.6": ["glucocorticoids"], "-1.9 9.1 6.3": ["agonizes"], "2.7 14.9 16.5": ["noblemen"], "-2.9 5.3 2.3": ["washings"], "10.2 9.6 11.6": ["puckering"], "24.9 9.0 8.7": ["moustachioed"], "7.3 -2.4 7.4": ["bookbuilding"], "-0.1 14.3 5.6": ["intimacies"], "6.7 6.2 48.4": ["pelagic"], "7.5 27.3 15.3": ["biotic"], "0.8 11.7 -6.2": ["disassociation"], "2.6 12.4 26.6": ["goldfinches"], "8.2 6.6 8.7": ["phonetics"], "-1.4 8.9 13.0": ["karst"], "7.2 9.3 21.7": ["chocolaty"], "1.5 5.3 16.5": ["mmt"], "-4.1 3.2 0.4": ["ultrasonography"], "-2.9 13.8 9.0": ["gefitinib"], "-2.9 4.8 11.4": ["annulments"], "-1.7 6.7 12.8": ["netminding"], "6.0 20.3 4.3": ["unworldly"], "3.8 6.9 3.2": ["cosmopolitanism"], "8.8 2.7 6.6": ["headboards"], "9.8 -0.9 10.9": ["anted"], "-0.1 13.9 8.0": ["sincerest"], "5.0 1.0 1.5": ["cs"], "3.1 -1.2 7.5": ["goldfields"], "0.7 0.7 8.0": ["bhajans"], "-3.6 2.4 2.3": ["matriculating"], "5.0 8.1 8.9": ["waterjet"], "0.5 14.3 12.4": ["crimeware"], "2.8 -3.6 10.0": ["anklets"], "6.9 4.6 7.2": ["gigatons"], "3.2 17.9 11.8": ["lathis"], "0.9 18.4 8.9": ["dichotomies"], "-1.3 20.0 6.1": ["ultramafic"], "-4.7 12.5 2.0": ["parities"], "8.3 11.8 14.5": ["hydrodynamic"], "2.7 1.4 13.6": ["ftp"], "0.3 3.0 10.6": ["volcanics"], "7.7 4.2 14.1": ["borax"], "2.3 1.4 10.1": ["prebiotics"], "2.2 6.7 11.7": ["refranchising"], "12.2 10.7 25.7": ["macaque"], "0.9 3.5 13.9": ["anklet"], "0.3 2.6 3.4": ["esters"], "-2.6 5.1 11.7": ["vog"], "-4.5 -2.1 12.0": ["arimoclomol"], "3.1 1.5 29.6": ["sweetbreads"], "9.9 3.5 20.9": ["crocks"], "-1.2 0.4 7.3": ["storytimes"], "14.0 4.0 26.5": ["mooching"], "-2.5 5.6 4.5": ["endotoxin"], "4.3 -3.6 -1.1": ["greened"], "5.2 6.2 6.0": ["enflamed"], "2.8 -0.5 0.5": ["sexualisation"], "5.7 17.4 8.2": ["materialization"], "4.9 12.3 5.0": ["loiterers"], "-7.0 -0.3 0.2": ["inj"], "10.7 7.5 4.8": ["truckin"], "-7.4 5.1 15.6": ["gravels"], "-3.3 -0.5 12.1": ["osteoblasts"], "3.3 -6.3 5.1": ["ses"], "11.7 1.6 3.4": ["initally"], "11.2 -2.3 13.2": ["herringbone"], "-0.4 7.0 2.7": ["dob"], "-5.5 6.1 7.9": ["placekicking"], "10.7 9.0 16.7": ["quays"], "7.1 11.8 18.6": ["stein"], "2.9 18.9 5.8": ["feigns"], "4.2 8.1 0.2": ["fervid"], "6.8 8.8 2.3": ["bedsides"], "-1.4 9.6 3.7": ["emollient"], "-2.2 17.7 6.5": ["chapped"], "-2.5 7.2 2.6": ["serums"], "3.2 11.0 3.6": ["wer"], "6.2 9.0 9.9": ["sabbath"], "5.7 0.1 14.5": ["headpieces"], "-2.0 1.7 2.0": ["pensioned"], "-7.8 9.0 14.1": ["overclockers"], "8.0 5.2 11.7": ["ryan"], "5.3 3.6 11.0": ["blowjob"], "2.1 6.8 -5.4": ["messageboard"], "7.2 5.1 39.8": ["oxtail"], "1.2 7.4 12.3": ["granodiorite"], "10.1 1.4 12.9": ["amore"], "8.1 9.0 -0.2": ["frm"], "11.3 -1.1 11.8": ["widgetry"], "-1.9 0.7 8.2": ["ruthenium"], "1.1 12.4 7.7": ["explicable"], "-3.7 19.9 6.3": ["sidearms"], "1.7 5.9 17.6": ["toques"], "-1.2 9.6 4.1": ["acheive"], "-10.6 5.8 16.8": ["snowpacks"], "7.8 21.6 3.1": ["iran"], "3.0 7.2 28.6": ["silkworms"], "-9.5 2.8 9.4": ["uprate"], "3.3 8.0 5.0": ["yttrium"], "0.0 11.1 22.9": ["jays"], "-1.2 -0.1 10.8": ["pico"], "3.7 16.3 6.1": ["slumlords"], "0.7 12.6 27.1": ["giblets"], "0.1 -0.3 5.3": ["rackmount"], "16.2 4.3 25.2": ["aggregations"], "-8.5 3.2 1.0": ["pruritus"], "-2.1 -0.1 -0.9": ["radiopharmaceuticals"], "-9.3 11.0 8.4": ["unaired"], "14.5 10.5 16.9": ["sledges"], "6.5 5.4 32.1": ["rookery"], "-4.2 9.0 4.4": ["gainful"], "-4.6 11.5 1.0": ["praxis"], "-3.5 -2.1 3.8": ["ostomy"], "6.7 6.0 37.0": ["lutefisk"], "-3.3 15.6 2.9": ["nonaligned"], "4.4 3.9 2.3": ["softs"], "15.5 7.8 11.7": ["tampers"], "-0.6 -2.3 5.1": ["datasheets"], "-5.5 3.4 24.3": ["robusta"], "10.0 -7.9 1.0": ["piquing"], "1.0 4.9 24.1": ["boathouses"], "0.1 13.5 6.3": ["complementarities"], "11.4 12.2 11.9": ["overtop"], "3.3 4.7 2.7": ["colostomy"], "13.7 3.9 6.5": ["scrawls"], "3.2 7.9 20.7": ["navels"], "5.1 0.7 27.8": ["homestyle"], "6.3 15.3 11.1": ["forbears"], "8.9 3.6 1.6": ["waaaay"], "-0.5 11.0 0.3": ["orthogonal"], "0.3 -2.9 9.6": ["paraxylene"], "0.9 4.7 12.0": ["edgewise"], "-5.6 11.6 7.2": ["sahib"], "9.0 2.8 16.9": ["showstopping"], "9.3 13.4 2.3": ["blustered"], "7.8 12.6 12.7": ["riptides"], "9.7 13.7 10.7": ["sulks"], "2.6 2.3 13.4": ["flappers"], "0.6 7.6 -4.6": ["soundproofed"], "4.9 4.7 8.2": ["ecstacy"], "4.3 9.4 4.6": ["fixations"], "5.8 7.8 11.7": ["ambien"], "5.3 17.3 4.4": ["mutinies"], "-9.4 7.6 6.4": ["reperfusion"], "22.8 2.7 12.9": ["roadrunner"], "10.0 16.1 4.8": ["deforming"], "11.4 8.7 3.6": ["matchwinning"], "7.5 9.2 1.8": ["monicker"], "2.3 3.0 11.8": ["middlebrow"], "-1.6 13.3 12.0": ["parvo"], "-11.3 7.9 2.1": ["committeemen"], "8.6 -7.0 -2.7": ["allays"], "-1.3 7.3 8.0": ["interweave"], "8.4 29.5 6.7": ["triangulating"], "16.4 8.2 14.5": ["doilies"], "6.9 -0.3 11.7": ["umbilicals"], "5.3 14.2 12.9": ["microtransactions"], "9.9 6.3 1.3": ["smolders"], "7.7 5.7 12.7": ["braceros"], "9.6 7.1 24.4": ["premade"], "17.0 14.5 12.6": ["sturdiest"], "9.3 10.2 14.7": ["subzero"], "15.4 4.1 0.1": ["intl", "questionmark"], "-2.3 -3.0 3.9": ["abandonments"], "5.8 10.2 6.7": ["rhythmical"], "0.5 8.2 6.4": ["flues"], "5.8 5.6 2.4": ["enviably"], "28.1 18.8 11.9": ["gremlin"], "8.8 13.8 7.0": ["unwired"], "16.5 11.0 10.3": ["portending"], "15.8 9.2 7.6": ["tableaus"], "12.7 7.5 1.4": ["rechecking"], "1.3 15.8 3.5": ["meridians"], "-1.5 6.8 3.6": ["poetics"], "-3.2 20.9 -1.2": ["demobilizing"], "-3.7 11.6 14.2": ["writerly"], "3.6 9.9 7.8": ["straphangers"], "-6.8 14.5 7.9": ["constitutionalist"], "1.7 5.2 6.7": ["microglia"], "11.7 -3.5 -2.1": ["announcment"], "0.2 12.5 1.3": ["suffragettes"], "7.0 4.9 10.2": ["flywheels"], "2.2 2.1 4.9": ["hryvnias"], "-2.6 9.2 0.5": ["farsightedness"], "3.4 6.3 11.5": ["vocalization"], "9.9 4.9 16.8": ["petticoat"], "8.2 1.8 17.8": ["microwaveable"], "11.3 7.3 9.5": ["potheads"], "10.5 -4.9 6.6": ["ao"], "7.5 3.9 5.9": ["hydrogenated"], "5.6 2.9 0.7": ["laundromats"], "-3.8 10.3 5.6": ["chukker"], "12.9 8.6 7.5": ["armoires"], "2.7 20.1 13.5": ["evolutionarily"], "6.2 18.6 -6.0": ["incarnated"], "18.3 13.5 10.4": ["spacemen"], "9.9 11.3 14.9": ["tarsands"], "-1.9 3.9 11.9": ["sanitarian"], "-2.7 6.0 -2.6": ["colognes"], "9.8 20.4 5.9": ["thunderbolts"], "-5.3 0.1 6.8": ["landfilled"], "9.3 8.2 10.8": ["bobsledder"], "6.3 6.1 27.5": ["meringues"], "6.7 -2.5 9.5": ["teabags"], "-1.2 4.4 8.0": ["stepgrandchildren"], "22.4 18.9 16.1": ["squishing"], "15.5 4.8 12.9": ["barbells"], "4.2 11.9 2.9": ["excising"], "7.0 11.6 9.3": ["torsion"], "6.6 10.6 3.8": ["discontents"], "-9.6 8.0 -4.0": ["hypoglycaemia"], "-3.0 9.8 7.6": ["percolation"], "2.5 15.0 1.5": ["psychosomatic"], "8.1 8.2 6.9": ["muscularity"], "3.8 7.3 9.6": ["dithers"], "4.6 4.5 16.7": ["nonstick"], "-1.0 13.2 6.4": ["upleg"], "5.3 11.0 23.4": ["jetski"], "14.0 19.4 21.4": ["creepers"], "6.3 2.6 2.5": ["asylums"], "18.1 5.3 5.7": ["govenment"], "7.6 5.6 9.5": ["finagled"], "-1.6 10.6 12.6": ["osteoclasts"], "5.2 16.6 9.9": ["ellipses"], "6.8 6.1 14.2": ["asphyxiating"], "18.6 8.9 18.3": ["whisperer"], "0.4 2.6 -1.5": ["negotations"], "7.6 10.4 4.7": ["anoraks"], "4.1 5.1 1.4": ["threepeat"], "4.2 2.2 13.6": ["witted"], "19.7 -3.4 15.4": ["belles"], "7.6 9.4 11.5": ["hangdog"], "12.0 14.9 9.1": ["oaf"], "-1.1 13.6 48.7": ["eelgrass"], "7.7 19.4 8.3": ["exult"], "4.5 5.1 2.1": ["referential"], "0.6 7.6 46.7": ["shorebird"], "3.6 -0.0 1.6": ["gangrape"], "6.0 9.2 14.9": ["schnauzer"], "-1.4 13.4 5.6": ["archly"], "14.3 -0.2 2.5": ["tromped"], "9.5 6.6 11.8": ["blueblood"], "4.9 1.5 7.4": ["str"], "9.4 8.1 7.3": ["wannabees"], "3.7 7.9 14.4": ["hospitalizes"], "-9.7 12.6 5.3": ["nonattainment"], "5.8 6.1 5.9": ["swop"], "4.2 10.8 23.3": ["wrens"], "6.2 -3.0 4.0": ["ultralow"], "9.2 18.2 7.6": ["omniscience"], "6.6 19.3 4.9": ["trifled"], "-5.6 7.2 13.9": ["galena"], "-4.7 7.3 -4.1": ["interchangeability"], "-1.9 13.4 12.9": ["drinkin"], "9.4 3.6 14.8": ["gumboots"], "-4.2 3.6 9.9": ["freeskiing"], "-1.3 1.6 2.4": ["nontechnical"], "14.5 1.5 9.8": ["mx"], "-9.5 3.7 0.5": ["troponin"], "-5.4 8.1 12.0": ["runout"], "1.6 6.0 8.8": ["uncontracted"], "1.9 7.3 0.6": ["unbuckle"], "3.3 5.8 3.4": ["bandmembers"], "4.5 -0.8 7.9": ["certifiers"], "1.4 14.8 17.6": ["fluorocarbon"], "5.7 21.9 6.5": ["abjectly"], "1.9 8.5 7.9": ["creasing"], "9.6 9.7 8.9": ["vexes"], "10.9 7.9 9.3": ["radii"], "10.0 2.8 20.1": ["sycamores"], "7.3 12.7 10.1": ["parsimony"], "21.1 18.5 25.7": ["octopi"], "2.4 15.8 -9.8": ["whereever"], "-2.3 11.9 14.7": ["cabotage"], "5.4 17.3 4.6": ["gluons"], "20.5 21.8 8.5": ["demigods"], "2.4 23.6 8.6": ["stratagems"], "4.8 6.2 1.3": ["coverups"], "-10.3 8.6 2.4": ["attributions"], "-12.3 13.9 4.3": ["deportable"], "3.7 4.8 11.8": ["abruptness"], "-4.1 22.8 12.2": ["poliovirus"], "11.4 22.9 8.1": ["electrocuting"], "8.7 4.2 44.0": ["nori"], "1.5 6.6 9.2": ["qigong", "nickeled"], "-2.7 1.6 12.9": ["jawline"], "11.6 4.6 16.6": ["creamer"], "11.4 2.0 13.7": ["palaeontologist"], "12.2 5.8 5.4": ["crisscrosses"], "4.2 8.9 -0.6": ["unbothered"], "8.6 6.7 23.5": ["dosa"], "24.9 16.5 10.4": ["snatcher"], "12.5 14.8 10.4": ["klutzy"], "8.9 -2.1 -3.5": ["nutritionals"], "6.6 4.9 17.7": ["stupa"], "2.3 9.3 -2.6": ["mistranslated"], "-2.5 21.1 4.6": ["militarizing"], "12.1 16.9 18.2": ["chucker"], "-0.4 12.2 14.1": ["albedo"], "-3.2 -4.1 2.9": ["educationalists"], "6.9 5.8 3.0": ["balderdash"], "7.0 6.2 19.0": ["tarmacs"], "10.0 -6.0 29.1": ["macadamia"], "3.9 19.6 15.5": ["tamarisk"], "-0.5 -0.1 5.0": ["overscheduled"], "-3.7 7.6 6.8": ["neurologically", "lessoned"], "5.8 -1.1 34.8": ["rigatoni"], "12.3 14.3 7.9": ["slinks"], "5.9 -2.4 3.1": ["cochair"], "-0.3 4.8 4.9": ["transacts"], "1.4 15.3 -2.4": ["aginst"], "-1.0 9.5 3.7": ["beatify"], "-2.3 1.7 7.9": ["flavonoid"], "1.6 8.7 11.2": ["sphincter"], "-1.2 19.6 8.7": ["nonproductive"], "7.3 11.3 12.0": ["ital"], "-1.7 5.2 18.6": ["joey"], "-3.4 12.2 1.4": ["plaint"], "-5.3 17.2 10.6": ["sallam"], "0.2 3.9 3.1": ["uncoupled"], "5.0 11.2 8.1": ["footlights"], "2.0 11.7 17.3": ["gloving"], "-1.6 3.2 -7.3": ["collateralize"], "3.9 9.7 8.0": ["dallying"], "7.7 7.4 18.6": ["trowels"], "5.2 2.8 15.9": ["herpetologist"], "16.2 14.1 5.2": ["hypnotically"], "-3.7 -6.4 -2.9": ["biopolymers"], "6.9 3.6 18.1": ["cho"], "4.6 13.6 9.0": ["thereupon"], "9.1 3.8 7.5": ["malaysia"], "8.0 3.6 0.1": ["mineralogical"], "2.8 -1.8 10.9": ["biennale"], "-6.7 16.4 11.2": ["indictable"], "13.7 3.6 8.7": ["tamp"], "8.6 5.9 15.1": ["shouty"], "-13.0 6.2 5.1": ["unexcused"], "6.4 10.2 3.1": ["firebrands"], "4.6 14.4 5.7": ["irrecoverable"], "4.3 2.8 7.2": ["armloads"], "0.6 9.6 14.6": ["indent"], "1.1 10.1 3.3": ["postmodernist"], "15.1 15.9 5.0": ["overheats"], "8.6 9.6 9.4": ["guiltily"], "3.6 11.8 7.7": ["soulfully"], "5.0 8.5 9.5": ["womans"], "8.3 12.1 16.5": ["leggie"], "15.8 13.2 5.3": ["herculean"], "15.9 3.3 5.3": ["downsizes"], "5.4 18.1 10.8": ["echolocation"], "-13.9 9.0 14.8": ["unenrolled"], "0.2 10.7 -0.4": ["activators"], "9.2 11.0 14.4": ["motormouth"], "1.4 15.2 13.3": ["nurturer"], "0.8 11.5 1.3": ["transferor"], "-1.4 5.7 -0.1": ["intervener"], "-1.5 19.1 3.2": ["intimidations"], "17.9 10.5 21.0": ["barker"], "14.0 1.8 9.6": ["minuet"], "8.8 24.1 6.0": ["legionnaires"], "5.7 8.8 8.2": ["constricts"], "3.8 7.6 9.8": ["evocatively"], "10.3 11.8 8.6": ["scorning"], "6.6 11.5 1.3": ["besmirching"], "-1.3 -4.6 2.4": ["predevelopment"], "6.0 1.7 12.6": ["sho"], "0.8 14.0 8.0": ["slugfests"], "-3.2 16.8 -3.5": ["immunotherapeutic"], "-0.2 5.7 29.5": ["tahini"], "25.5 12.4 23.1": ["pinatas"], "15.4 10.0 22.8": ["eatin"], "9.5 9.0 10.2": ["toffs"], "2.2 7.9 14.1": ["felicitous"], "-2.3 3.8 5.9": ["mattering"], "15.3 7.2 14.5": ["johnny"], "17.2 8.2 7.7": ["bilious"], "0.1 21.4 4.1": ["depreciable"], "-0.6 1.0 10.2": ["acromegaly"], "10.3 13.2 4.6": ["playsets"], "5.1 12.8 8.0": ["unrecovered"], "9.3 12.5 10.7": ["perforce"], "6.0 13.1 9.3": ["signifiers"], "0.3 8.9 -2.6": ["resemblances"], "9.8 6.8 28.3": ["eaglet"], "12.1 9.8 3.1": ["peepholes"], "9.9 8.1 5.3": ["teraflop"], "1.0 2.8 0.8": ["radiopharmaceutical"], "8.3 2.8 5.1": ["liveries"], "-0.5 13.8 2.6": ["apologia"], "-4.7 1.8 12.2": ["flowy"], "5.2 23.8 11.7": ["confiscatory"], "18.9 25.6 29.2": ["pincers"], "-0.7 20.3 5.0": ["distrusting"], "-8.2 28.8 4.4": ["equivocate"], "5.4 5.6 7.8": ["piffle"], "-2.9 1.6 -0.4": ["reaggravated"], "0.9 7.4 14.5": ["firehall"], "13.2 6.6 20.6": ["billy"], "5.1 10.8 12.8": ["warez"], "24.8 9.6 0.1": ["multibillionaire"], "-2.8 2.0 -0.7": ["professionalization"], "15.4 9.2 14.5": ["cutely"], "9.2 6.6 3.3": ["regathered"], "7.3 8.1 27.7": ["tai"], "2.3 4.3 10.2": ["rivulet"], "5.5 7.5 12.5": ["tonsil"], "-0.1 10.5 10.3": ["commingle"], "19.6 4.9 8.4": ["walmart"], "-8.9 2.8 11.1": ["onychomycosis"], "-4.9 8.0 5.6": ["yorked"], "-10.3 -1.4 5.5": ["showhome"], "0.9 13.9 0.0": ["locational"], "-0.9 0.3 12.6": ["mauka"], "-10.2 11.1 2.3": ["appointive"], "13.3 12.3 7.7": ["dweeb"], "11.7 15.1 25.6": ["rattlers"], "12.0 2.3 6.9": ["mantles"], "10.2 5.4 13.9": ["minuti"], "4.4 3.5 8.2": ["uplinking"], "10.7 3.3 8.8": ["girdles"], "-0.5 25.3 9.3": ["contras"], "0.1 0.6 -0.3": ["appraises"], "3.7 4.3 -1.2": ["controllability"], "-0.2 8.3 5.8": ["fiscus"], "5.7 11.0 5.8": ["mentalist"], "14.5 20.0 14.2": ["pussies"], "-3.0 2.3 6.2": ["skilling"], "3.2 6.0 9.1": ["urbanite"], "1.7 10.2 12.9": ["fullscreen"], "7.8 15.1 8.1": ["prozac"], "9.8 4.2 1.0": ["dealbreaker"], "8.4 2.5 8.3": ["paywalls"], "-7.2 1.3 5.3": ["knighthoods"], "7.9 23.5 9.0": ["unchallengeable"], "9.8 12.0 8.1": ["accreted"], "6.4 8.9 17.6": ["andy"], "8.1 1.1 30.1": ["shortcake"], "-9.9 8.9 2.8": ["comorbid"], "3.5 14.1 0.1": ["converses"], "0.9 8.9 6.0": ["hollerin"], "-0.7 7.9 14.4": ["hukou"], "1.0 5.0 8.8": ["expressionism"], "-7.1 6.4 -1.3": ["stridency"], "3.3 4.5 13.3": ["teats"], "-4.0 2.0 0.1": ["appearence"], "1.2 1.2 10.6": ["gamelan"], "6.6 3.1 16.6": ["tinges"], "1.7 4.9 -0.3": ["oder"], "-2.8 4.6 0.4": ["bookable"], "13.7 8.9 4.3": ["combi"], "9.5 17.0 13.2": ["verities"], "-1.3 13.1 5.5": ["astuteness"], "6.7 12.0 7.8": ["exactitude"], "2.6 -7.6 5.7": ["semiretirement"], "1.7 9.4 2.6": ["enflame"], "-1.8 14.0 5.5": ["forewarn"], "9.1 10.6 10.7": ["waterproofs"], "-3.9 5.5 0.3": ["perfumer"], "-3.4 5.5 7.8": ["shebeens"], "-0.7 10.7 8.3": ["mudroom"], "-8.4 7.1 -1.2": ["amiodarone"], "1.3 14.1 9.3": ["fullcourt"], "1.5 4.1 6.6": ["androgyny"], "3.4 6.0 14.0": ["cremating"], "-4.4 2.1 10.5": ["unicast"], "10.2 3.8 9.4": ["exhibitionists"], "-3.9 5.8 1.7": ["enought"], "4.9 8.1 10.6": ["buttering"], "13.4 5.2 1.5": ["prances"], "5.3 1.7 8.4": ["terabit"], "3.9 9.8 2.1": ["ablutions"], "7.7 3.6 12.2": ["sox"], "3.9 4.1 14.0": ["rectifier"], "5.8 11.8 12.9": ["rottweilers"], "6.1 16.9 19.1": ["dinks"], "-0.8 -1.9 -1.6": ["fundraised"], "11.6 5.0 18.7": ["fortuneteller"], "5.2 13.2 25.7": ["jake"], "1.7 9.7 28.8": ["vinegary"], "-5.1 -1.4 -1.8": ["mintues"], "3.6 19.1 11.5": ["defoliant"], "14.3 3.9 3.3": ["morethan"], "8.4 19.4 28.4": ["hyacinth"], "10.4 4.9 5.1": ["unsellable"], "7.8 13.6 9.0": ["nattering"], "9.5 5.6 5.5": ["snored"], "-5.3 7.9 16.5": ["ohana"], "1.3 4.8 -3.2": ["facelifted"], "3.1 3.0 5.9": ["bushing"], "1.1 15.3 8.3": ["despatches"], "4.4 11.1 6.2": ["politican"], "7.4 5.9 12.7": ["strop"], "-1.7 14.1 13.8": ["nakba"], "1.3 -1.8 2.4": ["dressmaking"], "-6.8 0.8 7.8": ["diluent"], "-4.9 11.5 9.5": ["outboxed"], "3.7 0.7 9.9": ["plateauing"], "1.6 9.9 7.9": ["gotchas"], "10.1 11.2 9.1": ["sticked"], "-6.0 2.8 3.8": ["limine"], "10.3 13.5 4.2": ["fountainhead"], "1.6 4.7 -2.7": ["appending"], "6.7 4.9 2.8": ["signages"], "4.1 -2.3 4.1": ["degradable"], "14.3 3.6 11.8": ["swishes"], "18.3 14.9 20.9": ["arachnids"], "2.7 -1.6 12.6": ["vicodin"], "2.7 4.1 0.9": ["synthesise"], "0.4 8.3 14.8": ["landside"], "-3.8 6.7 7.6": ["metallization"], "5.7 12.1 -1.2": ["defuses"], "13.0 9.9 9.4": ["metamorphose"], "4.0 -1.6 7.9": ["formwork"], "4.2 6.3 -1.0": ["reincorporation"], "5.8 8.5 2.4": ["sublimation"], "-0.7 8.6 13.8": ["colloquialisms"], "4.5 12.3 4.1": ["tommorow"], "6.6 3.1 13.8": ["trendiness"], "11.4 -0.6 8.2": ["trampolining"], "8.9 6.5 29.4": ["crisped"], "-5.5 4.6 1.8": ["citalopram"], "-5.9 -0.0 -1.0": ["homologated"], "-3.7 -1.6 4.3": ["amortizations"], "5.6 -0.3 13.7": ["headstock"], "-1.0 21.1 5.5": ["repetitiveness"], "-1.2 14.8 3.7": ["inputted"], "17.8 16.0 3.4": ["cretin"], "-3.7 18.7 15.1": ["adverb"], "-2.2 5.2 0.5": ["canonised"], "-9.5 3.6 3.2": ["quetiapine"], "3.3 1.3 4.6": ["hyperventilation"], "5.7 7.7 10.6": ["scherzo"], "10.4 -1.0 5.6": ["floodlighting"], "14.3 11.0 10.6": ["sightless"], "-5.9 6.5 15.3": ["anglophones"], "5.0 10.4 1.8": ["decisionmakers"], "0.6 6.0 10.4": ["folkies"], "9.8 9.8 6.9": ["governemnt"], "9.2 15.5 4.2": ["faultline"], "-7.3 1.3 -1.9": ["publishable"], "3.9 15.9 8.6": ["fetters"], "2.6 9.4 38.3": ["calzone"], "-0.6 7.5 6.8": ["overdrawing"], "-8.0 2.8 6.3": ["pretreated"], "9.3 -5.4 7.7": ["houseware"], "4.1 3.5 6.5": ["zeolite"], "13.2 11.5 27.0": ["rutabaga"], "13.5 15.7 8.5": ["jovially"], "8.9 11.6 -0.1": ["germany"], "10.6 14.0 8.1": ["untying"], "2.7 16.1 9.3": ["subtlest"], "-9.4 14.4 8.6": ["singleness"], "3.5 -0.3 9.9": ["microblogs"], "-6.3 11.0 5.0": ["epistle"], "4.0 8.6 5.0": ["spelunking"], "3.4 6.0 6.2": ["amines"], "6.9 19.1 -0.4": ["conflagrations"], "2.2 14.5 5.7": ["tractable"], "16.4 3.1 3.5": ["corporatization"], "-2.0 -0.6 2.5": ["opportunties"], "-8.4 1.2 4.3": ["loanees"], "-2.3 8.6 13.7": ["crankiness"], "5.2 10.1 9.5": ["cellblocks", "theese"], "1.2 12.6 5.0": ["whereof"], "21.3 14.9 0.4": ["hoaxer"], "10.0 16.7 8.9": ["axeman"], "13.2 12.2 22.5": ["pinecones"], "4.4 3.5 11.1": ["bridles"], "3.0 11.4 6.9": ["canvasser"], "1.8 2.2 6.7": ["nie"], "1.8 7.9 14.8": ["reseeded"], "11.4 26.6 8.9": ["weaponize"], "3.7 20.2 4.1": ["basest"], "1.2 17.3 0.9": ["hindus"], "3.6 8.9 13.5": ["gentrifying"], "0.5 7.2 16.9": ["interbreed"], "-3.2 4.2 -2.3": ["cotinine"], "-2.3 -0.5 3.7": ["flextime"], "16.9 27.0 7.3": ["malefactors"], "13.5 12.1 3.0": ["playset"], "4.6 3.2 -0.7": ["relight"], "0.8 6.3 22.0": ["crofters"], "3.9 5.6 6.6": ["skype"], "2.2 4.9 20.7": ["jackup"], "2.7 -3.2 -0.0": ["muh"], "9.3 6.0 8.1": ["chiral"], "9.7 4.7 18.6": ["yuk"], "8.3 -1.3 9.1": ["weirded"], "8.3 -2.5 8.9": ["unspooled"], "-8.1 33.2 11.6": ["noncombatant"], "4.2 20.1 2.7": ["possessors"], "-5.1 8.2 5.8": ["allopathic"], "2.2 6.3 11.7": ["shopowners"], "1.6 31.6 -0.3": ["unbelieving"], "6.4 5.5 11.7": ["drawled"], "-0.7 1.1 13.7": ["sala"], "18.1 7.3 18.2": ["munches"], "5.5 10.3 14.8": ["nightingale"], "7.6 2.0 4.7": ["myki"], "7.9 19.1 7.5": ["awaking"], "-1.8 4.5 5.6": ["chemokines"], "0.8 8.3 10.8": ["nitpicky"], "6.7 13.5 14.5": ["incised"], "14.9 2.4 1.3": ["nickle"], "0.1 9.6 2.9": ["accumulators"], "9.5 10.1 11.2": ["squib"], "-11.5 10.0 8.1": ["redistricted"], "-2.6 5.0 5.8": ["hydrolysis"], "2.6 16.8 2.5": ["potshot"], "16.3 4.6 20.3": ["dildos"], "6.0 11.7 10.7": ["uhm"], "4.5 3.6 3.4": ["gofer"], "-0.5 4.3 9.5": ["commonsensical"], "5.2 2.5 -3.0": ["mandatorily"], "2.8 6.3 1.2": ["rankling"], "15.0 7.0 16.0": ["jackknife"], "6.8 10.3 7.8": ["whippings"], "4.9 0.6 6.2": ["thefirst"], "-3.0 1.1 9.9": ["comped"], "0.7 2.7 11.1": ["retouch"], "8.0 4.7 12.3": ["bandy"], "-11.5 3.0 15.0": ["genistein"], "6.6 12.9 4.0": ["trillionth"], "3.9 3.1 -0.2": ["slagged"], "4.6 10.9 1.5": ["alderwoman"], "17.1 12.1 14.7": ["mastodons"], "-1.8 1.9 5.1": ["townsite"], "13.4 7.1 12.0": ["overambitious"], "0.2 9.3 12.1": ["feminization"], "-5.6 13.4 4.7": ["ibn"], "0.2 14.8 4.2": ["politcal"], "5.7 12.8 2.2": ["incapability"], "-3.9 10.2 8.6": ["explication"], "16.1 5.2 8.4": ["vender"], "4.2 4.2 12.5": ["fringing"], "8.6 13.7 5.8": ["insultingly"], "14.1 20.1 7.5": ["toadies"], "10.9 1.7 15.0": ["alex"], "3.7 6.8 12.1": ["wot"], "7.5 6.7 4.7": ["metronomic"], "2.8 7.0 21.7": ["joist"], "14.0 4.6 16.3": ["paperclip"], "12.4 15.3 3.7": ["vivisection"], "7.9 13.0 14.2": ["burrs"], "7.4 7.5 3.6": ["tensely"], "4.4 -2.8 11.8": ["gabfest"], "-2.9 1.2 6.9": ["limiters"], "-5.2 4.3 6.7": ["salmeterol"], "5.5 13.5 5.8": ["insupportable"], "3.8 -0.3 2.2": ["eq"], "-2.2 -2.0 9.4": ["monocrystalline"], "-2.3 9.8 8.7": ["irrigates"], "-10.4 -4.6 10.6": ["stoles"], "-4.2 3.9 9.2": ["landfilling"], "-8.2 0.7 -1.8": ["cowrote"], "3.7 8.0 10.9": ["jason"], "14.3 13.4 15.7": ["flatfooted"], "-7.0 1.9 4.9": ["prostaglandins"], "8.0 13.7 4.5": ["hearten"], "6.4 5.7 13.4": ["rambler"], "-6.0 11.1 -2.2": ["straightforwardness"], "17.4 6.2 15.6": ["sloths"], "17.6 18.1 14.1": ["footstool"], "-7.1 2.6 11.9": ["remortgages"], "-6.9 5.3 -4.8": ["spirometry"], "9.3 24.0 9.1": ["globalists"], "8.3 -0.2 12.1": ["fabulousness"], "-0.1 5.3 11.4": ["funnymen"], "13.7 15.0 9.7": ["lumpen"], "-10.4 2.9 15.7": ["arabica"], "-9.9 8.6 4.0": ["hospitalize"], "9.1 4.0 11.0": ["drawcards"], "-2.8 -2.1 5.9": ["detoxing"], "9.3 10.8 8.6": ["rainmakers"], "-0.6 8.4 17.4": ["repopulation"], "17.3 2.0 4.2": ["lovechild"], "9.7 11.0 7.9": ["jabber"], "-12.5 2.2 7.7": ["debridement"], "-3.4 1.9 3.1": ["prothonotary"], "3.4 10.9 17.6": ["kanji"], "18.1 9.0 3.3": ["throbbed"], "2.9 20.6 8.4": ["blitzers"], "-3.5 9.7 3.3": ["epitopes"], "2.1 -1.5 10.1": ["tc"], "5.3 15.2 13.7": ["workpiece"], "13.9 6.6 16.6": ["dow"], "5.9 5.9 5.6": ["postmistress"], "3.3 6.3 8.8": ["brittleness"], "-11.3 0.1 8.7": ["synods"], "3.0 9.9 12.0": ["penknife"], "8.9 1.8 10.8": ["glaciologist"], "-1.9 14.5 -1.8": ["inflammable"], "-2.0 10.1 6.6": ["radioisotope"], "9.8 7.7 2.3": ["misters"], "10.1 5.4 8.7": ["blissed"], "3.7 12.1 17.2": ["causeways"], "7.8 11.3 6.6": ["mineshaft"], "0.4 3.3 4.3": ["disadvantaging"], "3.9 3.2 7.6": ["shims"], "-5.7 11.4 8.7": ["stoping"], "-0.4 5.0 7.9": ["evictees"], "7.5 16.4 10.5": ["goodhearted"], "7.2 2.1 42.9": ["chanterelles"], "-1.9 3.8 6.9": ["plebiscites"], "-1.2 20.1 -0.4": ["justness"], "0.3 9.5 43.1": ["ladyfish"], "-4.6 3.5 32.5": ["moorage"], "0.8 3.7 7.1": ["mot"], "1.4 10.8 7.6": ["brooded"], "3.2 7.8 9.4": ["dilatory"], "1.5 15.8 1.0": ["mischaracterizations"], "-5.9 7.6 10.0": ["boardercross"], "0.7 -5.2 8.5": ["polyolefin"], "7.5 9.3 9.3": ["clampers"], "-8.7 11.0 9.7": ["unawareness"], "-7.8 2.0 9.5": ["printmakers"], "6.4 12.8 5.9": ["symmetrically"], "0.3 0.5 8.2": ["meticais"], "1.0 25.7 12.2": ["datum"], "-0.6 4.5 6.7": ["ini"], "5.5 8.8 16.5": ["irish"], "2.6 12.7 4.0": ["humiliatingly"], "0.4 -1.2 4.8": ["underqualified"], "4.1 -4.0 10.9": ["municipally"], "-5.9 2.3 2.2": ["vaginally"], "-1.0 8.1 6.3": ["freestylers", "seroprotective"], "10.5 7.9 2.0": ["reengineer"], "-10.1 1.5 9.3": ["mikvah"], "7.8 0.5 7.8": ["alle"], "0.1 7.7 -1.2": ["defecit"], "7.6 11.9 15.7": ["reassembly"], "4.7 15.5 6.2": ["rubbles"], "-1.2 17.8 2.8": ["unlearned"], "10.3 -0.5 11.6": ["windbreakers"], "3.2 5.9 17.0": ["oscar"], "3.4 2.1 13.0": ["sarcophagi"], "-1.4 3.6 13.4": ["blander"], "2.3 9.0 5.3": ["catchiest"], "0.8 -0.2 9.9": ["shinbone"], "11.3 7.3 27.6": ["undersize"], "-5.5 14.2 -3.3": ["dispossessing"], "7.1 9.6 18.9": ["taiko"], "-1.2 10.6 36.8": ["spearfishing"], "5.5 10.7 3.3": ["cryin"], "2.8 6.2 0.1": ["vaguer"], "6.6 15.3 -0.9": ["figments"], "10.1 0.0 8.5": ["february"], "-1.0 -0.6 2.3": ["zolpidem"], "4.0 4.0 7.3": ["bottlenecked"], "-1.8 4.7 6.3": ["erythema"], "14.1 -0.9 8.0": ["kazoos"], "-0.5 14.8 -2.8": ["unburden"], "-7.2 6.7 18.1": ["natin"], "-5.3 5.0 8.4": ["mortgagees"], "2.3 4.3 5.7": ["undergird"], "5.9 3.4 3.5": ["eine"], "10.3 18.9 14.7": ["decimates"], "15.8 -6.0 4.6": ["misbranding"], "2.4 10.4 4.8": ["astronautics"], "4.4 -0.2 3.2": ["brainstorms"], "7.4 -0.7 12.7": ["wei"], "-3.5 7.2 2.4": ["inhalant"], "2.2 6.5 11.7": ["bergamot"], "1.8 12.3 6.7": ["evocations"], "5.0 -2.4 4.3": ["buzzworthy"], "4.6 14.2 2.6": ["objectify"], "2.8 10.0 9.3": ["megatonnes"], "26.5 7.8 13.5": ["thingies"], "-1.1 5.0 17.7": ["bingos"], "3.0 6.0 9.4": ["nonpolluting"], "-5.8 4.7 -7.2": ["angiograms"], "12.2 18.5 10.2": ["supercarrier"], "5.4 10.0 9.2": ["clubland"], "2.4 3.5 -2.6": ["straggled"], "18.8 4.0 13.8": ["foo"], "9.0 12.6 4.5": ["sublimated"], "10.2 12.3 12.2": ["chancing"], "-0.8 3.1 8.9": ["unspools"], "-2.8 15.8 5.3": ["vaccinators"], "5.4 11.5 11.8": ["nuthin"], "9.3 4.5 4.2": ["druggist"], "-1.1 8.1 12.8": ["microtubule"], "5.0 11.5 8.5": ["rem"], "6.3 20.4 3.8": ["uncatchable"], "15.3 12.3 5.0": ["whingers"], "-0.6 8.6 7.6": ["importations"], "-9.4 8.4 4.5": ["cytotoxicity"], "-2.2 4.8 -2.7": ["reassume"], "-1.4 8.2 25.2": ["eutrophication"], "-1.8 8.0 8.7": ["tory"], "-2.4 -3.4 5.2": ["microloan"], "-2.6 3.2 14.2": ["smallholder"], "20.6 11.6 3.8": ["unlovely"], "14.2 15.3 14.2": ["wretch"], "5.6 18.3 7.1": ["wretchedness"], "5.9 9.7 0.8": ["airbus"], "14.5 14.5 38.3": ["anemones"], "7.7 4.3 11.8": ["bodices"], "7.6 13.6 10.2": ["geekdom"], "1.4 10.0 13.3": ["collaring"], "-8.7 0.2 2.3": ["elopement"], "4.7 5.8 23.3": ["nippers"], "9.5 12.3 15.4": ["schlub"], "-6.4 9.9 7.0": ["elapses"], "0.6 -0.2 0.1": ["microsystems"], "1.7 10.8 9.4": ["declawing"], "9.6 9.7 7.9": ["nebulae"], "3.0 14.1 8.8": ["ontological"], "16.2 16.8 7.8": ["archetypical"], "5.0 14.1 5.7": ["interceding"], "1.2 3.6 4.8": ["horsewoman"], "1.1 4.3 12.1": ["rockfalls"], "4.9 4.5 16.6": ["quo"], "4.2 6.0 16.5": ["distractingly"], "0.5 3.8 12.9": ["dormers"], "7.3 15.1 17.6": ["similes"], "21.8 9.0 16.6": ["semicircular"], "13.1 11.7 10.5": ["adder"], "-2.9 5.7 11.5": ["navigability"], "7.2 0.5 -0.1": ["tieing"], "8.5 0.5 5.1": ["colorized"], "4.6 5.2 12.5": ["roids"], "-3.8 2.9 3.3": ["carpooled"], "-1.9 3.5 10.5": ["frescos"], "-6.7 5.7 17.4": ["stouts"], "9.2 5.8 6.9": ["tackiness"], "-1.0 2.1 16.4": ["subpopulation"], "-12.8 6.2 7.2": ["anthracyclines"], "-12.5 5.2 24.2": ["viognier"], "9.7 4.4 2.4": ["frameless"], "6.4 12.3 23.0": ["currant"], "10.6 2.7 11.1": ["winder"], "4.7 10.4 4.3": ["semantically"], "-1.0 11.2 4.2": ["grammatically"], "-1.4 10.6 -2.3": ["fettered"], "8.8 5.0 2.1": ["grafitti"], "1.3 16.4 9.9": ["kinfolk"], "11.1 19.4 8.6": ["commissars"], "14.1 11.6 14.9": ["thar"], "2.3 5.4 8.4": ["singin"], "-3.3 -6.3 7.4": ["philatelic"], "12.0 12.3 1.7": ["murderess"], "4.7 18.0 7.9": ["dismounting"], "-1.2 38.0 8.6": ["wingmen"], "6.7 9.6 11.2": ["maulings"], "-2.5 9.0 2.1": ["undertrial"], "5.3 8.8 9.6": ["childishness"], "14.8 9.3 8.4": ["oracles"], "3.9 21.6 4.8": ["yardages"], "3.8 11.3 6.5": ["suppressor"], "9.0 17.4 12.8": ["xenophobes"], "0.4 1.2 6.8": ["rhinitis"], "-7.4 8.8 4.0": ["consistencies"], "13.7 3.4 25.3": ["lidded"], "12.3 6.7 3.0": ["castrating"], "-5.4 15.5 10.2": ["idealize"], "0.1 4.4 8.8": ["phytoestrogens"], "8.8 17.5 24.3": ["grackles"], "-6.1 4.0 7.4": ["multithreading"], "1.1 6.7 1.5": ["perturb"], "-6.0 7.4 -5.9": ["deplaned"], "10.4 5.1 -0.4": ["railyards"], "-7.3 5.4 13.4": ["raceable"], "7.8 14.4 3.6": ["outslug"], "-0.5 3.7 6.7": ["biasing"], "-12.1 2.6 -2.7": ["escrows"], "8.2 8.0 11.2": ["banisters"], "7.0 0.8 14.3": ["sunbathed"], "-6.8 9.8 1.6": ["amperage"], "10.7 11.7 -2.4": ["importuning"], "-12.1 8.5 2.1": ["arounder"], "1.0 6.9 11.0": ["storyboarding"], "6.7 10.5 7.4": ["newswoman"], "-6.7 3.5 7.0": ["milan"], "20.7 9.1 9.9": ["flatlining"], "4.5 6.1 27.3": ["paddies"], "10.5 27.0 3.8": ["bazookas"], "11.1 13.3 15.7": ["movistar"], "-2.3 2.2 8.7": ["buttonhole"], "17.5 12.3 12.0": ["gangrenous"], "-10.2 5.3 17.1": ["homesite"], "0.9 5.0 6.4": ["timbres"], "-3.8 1.5 -4.3": ["psychometric"], "2.9 -1.3 10.2": ["mandolins"], "3.7 3.9 1.6": ["makeweight"], "-1.4 9.5 32.9": ["tidewater"], "6.8 7.9 7.7": ["godman"], "7.7 0.9 29.8": ["frites"], "-2.4 8.2 8.3": ["contrapuntal"], "0.8 3.1 8.1": ["ble"], "0.5 0.8 -1.7": ["breathalyzers"], "5.5 4.6 6.6": ["preis"], "2.8 11.7 10.5": ["cybersex"], "-4.1 9.6 11.1": ["downtrends"], "8.0 -2.7 26.3": ["shingled"], "-0.4 2.2 3.3": ["voidable"], "4.2 16.5 2.2": ["aerosolized"], "2.6 13.7 -0.9": ["diasporas"], "0.5 3.5 6.8": ["handphones"], "5.7 -1.2 13.8": ["vellum"], "6.0 4.7 5.7": ["sidelight"], "13.2 3.9 5.2": ["salivated"], "5.3 3.2 3.6": ["manageress"], "11.6 19.0 8.1": ["spacecrafts"], "1.1 8.3 10.5": ["swingarm"], "12.9 36.4 7.5": ["satan"], "2.5 21.1 4.9": ["intuit"], "-2.1 9.1 9.2": ["allrounders"], "6.8 12.1 10.3": ["thither"], "9.6 19.1 17.6": ["woodsman"], "6.6 4.8 10.3": ["yuks"], "-1.2 7.2 16.0": ["unripe"], "0.2 14.6 9.4": ["exiling"], "6.3 11.0 15.4": ["chlorofluorocarbons"], "-2.3 1.4 37.2": ["scaup"], "15.6 17.3 9.3": ["blotch"], "3.8 11.7 -2.2": ["anteroom"], "1.0 7.2 11.6": ["sig"], "7.9 -2.2 11.9": ["modish"], "8.2 7.2 21.9": ["suppertime"], "18.1 2.6 12.2": ["extruder"], "-4.4 25.4 11.3": ["singleplayer"], "-3.3 9.5 1.5": ["undershooting"], "-6.1 8.7 2.5": ["uncared"], "25.5 5.4 12.2": ["pyramidal"], "3.4 3.4 4.0": ["gravediggers"], "5.2 5.9 14.2": ["sprocket"], "8.5 3.6 5.3": ["depts"], "-7.1 11.3 2.9": ["collocated"], "1.4 14.6 9.4": ["geocache"], "10.4 19.9 12.7": ["flys"], "4.7 10.2 10.0": ["subsegment"], "-2.0 13.4 16.9": ["heathland"], "-0.9 5.7 11.5": ["antiquarian"], "4.5 12.6 -1.1": ["turbulences"], "9.4 11.4 -1.6": ["hasn"], "10.3 7.7 12.0": ["embezzler"], "2.3 15.6 8.3": ["unpreparedness"], "2.8 26.4 4.8": ["debilitate"], "-2.5 15.8 4.5": ["fring"], "18.2 5.5 41.4": ["crawdads"], "3.9 11.3 16.5": ["landforms"], "8.1 6.2 0.7": ["hoopster"], "4.4 -1.3 -2.5": ["performace"], "4.6 12.1 16.4": ["mounding"], "6.2 5.0 11.5": ["emulsifiers"], "-0.3 -2.9 16.1": ["hoodia"], "17.0 2.0 5.8": ["wazoo"], "6.9 3.7 5.7": ["kitchenettes"], "-2.0 16.8 -1.6": ["safehouses"], "0.8 15.4 20.8": ["gamey"], "2.5 -0.4 12.3": ["tourmaline"], "5.4 5.4 8.6": ["nostrums"], "7.6 5.2 32.1": ["nightcrawler"], "-5.6 -5.0 0.0": ["readmit"], "4.2 -2.0 6.1": ["schmoozed"], "11.3 9.6 17.5": ["wipeouts"], "2.2 14.7 16.4": ["gardenia"], "-3.2 -0.8 -0.1": ["budesonide"], "-5.0 6.8 13.0": ["downspout"], "0.6 20.4 7.5": ["unlikeable"], "-7.1 6.1 -1.6": ["reappraised"], "5.4 6.2 9.7": ["doozies"], "3.0 11.8 10.3": ["undercounting"], "12.2 24.0 8.5": ["intimidator"], "-10.0 9.4 5.1": ["routings"], "10.7 -1.5 10.6": ["tn"], "5.0 11.8 3.7": ["looney"], "4.3 1.2 13.4": ["mobo"], "1.0 11.8 8.1": ["lengthiest"], "15.4 11.0 8.7": ["juking"], "0.1 11.8 26.6": ["rotenone"], "-0.4 7.7 12.2": ["blaxploitation"], "17.2 4.1 8.0": ["tec"], "12.3 22.1 15.5": ["huntsman"], "2.8 2.9 -4.1": ["intercoms"], "-6.9 -4.2 0.8": ["lipodystrophy"], "-2.6 -1.9 3.6": ["intrauterine"], "7.8 18.9 5.5": ["individualists"], "6.9 4.6 4.6": ["ua"], "15.1 13.6 1.2": ["whooshing"], "7.7 24.6 12.2": ["nonhuman"], "-2.7 2.4 5.8": ["sickout"], "-2.8 3.6 9.9": ["eligibles"], "7.8 8.7 29.7": ["peregrine"], "2.0 6.8 19.4": ["methylamphetamine"], "-2.2 6.0 11.6": ["dupatta"], "5.0 6.4 2.2": ["crassness", "yound"], "-2.6 6.1 3.3": ["comptrollers"], "8.3 4.1 19.3": ["shipshape"], "1.9 11.7 12.4": ["aureus"], "9.1 11.0 11.4": ["hesaid"], "-10.4 5.4 18.7": ["malbec"], "2.4 17.8 10.4": ["clade"], "13.2 12.7 9.8": ["wierd"], "-2.5 13.2 9.8": ["isolations"], "2.9 -9.5 5.0": ["tah"], "2.6 -5.8 10.6": ["shindigs"], "-2.5 10.9 4.3": ["redound"], "1.2 0.0 15.2": ["barite"], "-0.1 11.1 9.5": ["hotfix"], "7.7 0.8 3.5": ["rorts"], "1.0 4.2 5.1": ["curiousity"], "-0.4 24.3 11.0": ["tamils"], "7.1 12.1 -2.1": ["damns"], "6.5 19.8 4.0": ["dieing"], "-5.3 7.8 17.2": ["daypart"], "-5.9 2.7 29.4": ["minestrone"], "6.5 2.9 6.5": ["fishtailed"], "13.9 11.2 3.3": ["unzipping"], "0.7 0.7 13.6": ["discolouration"], "-3.0 20.6 20.1": ["plebe"], "13.1 13.0 10.0": ["alchemists"], "7.6 8.4 13.5": ["goths"], "14.4 4.6 10.0": ["walkin"], "0.4 9.0 -6.8": ["unrests"], "2.5 2.1 9.8": ["phospholipids"], "-2.6 4.0 29.9": ["tenderloins"], "-5.2 -0.8 -0.6": ["obligors"], "6.8 4.9 6.9": ["boilover"], "5.5 7.2 5.9": ["resonators"], "8.9 0.2 9.7": ["fiberboard"], "9.2 3.5 3.5": ["laneways"], "10.8 -6.9 -11.4": ["conjuction"], "-9.3 2.3 -0.5": ["decommitted"], "15.1 6.8 17.6": ["sheers"], "0.5 -0.3 5.3": ["hyperbaric"], "14.5 8.4 11.6": ["extractors"], "1.0 15.4 12.2": ["seedbed"], "12.1 12.9 32.7": ["peeler"], "7.9 8.9 11.4": ["haulier"], "15.7 18.0 19.0": ["fanged"], "-3.0 10.3 11.9": ["hutments"], "13.7 12.3 7.2": ["subatomic"], "9.8 -3.6 21.9": ["chuckwagon"], "-0.5 13.7 -1.1": ["crashworthiness"], "4.1 7.0 9.8": ["morticians"], "10.5 -1.5 14.1": ["jon"], "14.7 21.4 11.2": ["gestalt"], "-3.5 22.1 6.4": ["volition"], "-4.4 7.8 20.6": ["septage"], "2.8 3.0 8.3": ["checkmark"], "-3.8 0.2 -1.7": ["apprising"], "0.5 10.2 9.1": ["matatus"], "7.8 -1.7 10.6": ["temping"], "6.8 -0.2 6.5": ["cleanout"], "3.1 5.6 13.6": ["grayed"], "-3.7 7.6 1.3": ["stuffiness"], "-1.4 6.1 6.4": ["canoed"], "4.3 11.4 7.4": ["bafflingly"], "3.1 -2.1 0.2": ["examinership"], "4.1 9.7 8.0": ["bitched"], "14.8 32.8 26.7": ["borers"], "10.8 12.0 10.1": ["chavs"], "-2.1 7.5 8.3": ["dudu"], "2.2 13.8 5.3": ["grimness"], "8.5 10.8 23.4": ["pupae"], "-0.8 7.3 8.3": ["allergists"], "6.0 1.8 34.5": ["seine"], "-0.7 0.7 7.9": ["abbreviate"], "15.4 24.2 11.5": ["tripwire"], "-8.4 -2.9 8.7": ["hydrocracker"], "6.0 -2.1 6.4": ["sd"], "-0.1 5.7 -3.6": ["videocassettes"], "7.0 6.9 31.6": ["buttercream"], "13.3 11.7 29.3": ["chickadee"], "-0.8 5.1 1.6": ["extranets"], "-2.9 25.5 10.2": ["wadi"], "9.3 12.3 15.2": ["drenches"], "4.2 13.7 9.2": ["outfields"], "18.8 12.6 6.2": ["noisemaker"], "-7.1 -1.0 5.8": ["downpayments"], "16.4 24.5 14.5": ["fuckers"], "13.2 11.5 -6.8": ["refashioning"], "3.6 5.9 3.1": ["legislates"], "4.5 7.1 6.3": ["cowshed"], "8.6 2.0 8.6": ["overindulged"], "7.6 20.1 19.4": ["superkick"], "6.5 3.5 -0.8": ["biomolecular"], "6.3 8.9 31.2": ["guppies"], "-2.3 26.7 6.0": ["micromanager"], "13.5 10.8 11.3": ["redraws"], "3.7 1.9 12.9": ["harebrained"], "10.6 10.3 12.4": ["sears"], "-0.2 2.3 -4.6": ["recommitting"], "6.3 8.0 11.2": ["bloodstain"], "-3.1 7.4 2.4": ["undershirts"], "-1.9 7.3 2.3": ["federate"], "21.0 7.1 5.5": ["hoover"], "19.3 14.5 10.4": ["dirigible"], "1.4 1.4 5.8": ["soms"], "-3.5 12.8 17.2": ["malathion"], "0.8 5.8 14.8": ["grottoes"], "-1.7 12.0 -0.9": ["excommunicate"], "21.1 6.4 13.5": ["belches"], "-0.4 4.3 9.4": ["immunoassays"], "8.7 9.9 18.0": ["beveled"], "-10.0 2.4 10.9": ["intramuscular"], "19.3 6.8 3.0": ["adspend"], "2.5 4.4 6.6": ["steepen"], "4.6 6.1 4.9": ["colonia"], "1.7 8.7 22.0": ["turbid"], "5.8 5.1 15.7": ["vmware", "pyritic"], "-3.1 14.4 5.4": ["followership"], "16.7 13.5 10.0": ["slumbers"], "-2.0 10.2 0.6": ["tachycardia"], "-2.8 0.6 2.3": ["restaged"], "-2.8 11.0 3.7": ["formalism"], "4.1 11.3 4.6": ["buttoning"], "7.6 10.7 10.3": ["hayfield"], "3.5 7.2 4.8": ["unretired"], "6.4 9.6 1.6": ["stile"], "12.3 9.4 10.8": ["kingly"], "0.5 9.0 44.0": ["leatherbacks"], "-0.1 2.6 6.7": ["condensers"], "12.5 13.3 0.6": ["blowin"], "6.2 -2.2 6.8": ["dit"], "-14.1 10.3 -0.0": ["undertreated"], "-5.5 3.2 -7.5": ["rapporteurs"], "-1.0 3.2 12.9": ["walang"], "5.5 5.0 8.7": ["infocomm"], "5.4 13.0 5.1": ["reflate"], "-1.7 17.0 9.2": ["robocall"], "13.7 7.6 13.9": ["steelwork"], "-3.2 3.9 0.1": ["itvt"], "0.9 21.5 5.7": ["irreducible"], "3.3 5.8 -1.9": ["tommorrow"], "-7.8 3.2 6.5": ["sates"], "0.3 14.1 8.8": ["offhandedly"], "-2.0 8.4 3.3": ["bolded"], "3.5 1.1 23.7": ["snapdragons"], "8.9 1.7 5.7": ["outgrows"], "15.2 1.1 16.2": ["stuffers"], "4.9 -0.7 3.5": ["pharmacodynamics", "etter"], "4.2 18.6 9.3": ["masochists"], "-9.3 -0.7 8.8": ["cantors"], "2.4 6.2 0.8": ["indubitably"], "-7.0 11.4 11.7": ["lithologies"], "8.2 8.0 22.7": ["soju"], "-3.0 2.3 14.6": ["twill"], "-5.9 11.8 12.7": ["viticultural"], "11.7 10.0 11.1": ["breakdance"], "18.6 16.4 14.7": ["amigo"], "18.4 16.1 20.3": ["warthog"], "0.7 2.8 10.8": ["methionine"], "13.8 7.2 3.3": ["interweb"], "-5.7 4.2 4.7": ["committeewoman"], "-3.9 9.7 17.8": ["superfecta"], "-2.3 -3.6 8.2": ["electrolytic"], "3.4 12.7 15.5": ["avast"], "2.0 2.4 24.7": ["mangosteen"], "-0.5 7.3 10.2": ["betrothal"], "-3.3 10.9 11.1": ["mafic"], "-12.1 -1.0 5.1": ["municipals"], "8.9 6.9 12.7": ["maddest"], "4.8 7.0 14.1": ["yeasty"], "-0.1 15.2 14.5": ["nahi"], "-7.5 7.7 11.3": ["endometrium"], "-1.2 19.5 12.6": ["counterpunching"], "16.6 2.9 2.1": ["busines"], "-0.5 -0.7 8.5": ["nanocomposites"], "10.1 16.9 11.6": ["dickhead"], "3.6 0.3 4.5": ["kcal"], "2.7 7.9 8.4": ["lensman"], "6.1 3.7 4.9": ["firmwide"], "16.5 5.1 7.2": ["curvilinear"], "3.7 5.6 2.5": ["chorused"], "10.7 8.2 6.7": ["sclerosis"], "-3.4 7.8 19.0": ["reovirus"], "11.8 13.5 13.0": ["posties"], "0.5 1.5 14.7": ["shellac"], "5.0 10.0 21.9": ["oarsmen"], "-0.5 8.2 8.3": ["handlooms"], "-1.5 3.3 6.1": ["hydrogeologist"], "6.7 14.2 15.2": ["closeups"], "6.0 12.5 6.9": ["teleprompters"], "14.6 3.7 10.5": ["windpower"], "-13.3 14.8 -1.7": ["wrongfulness"], "2.5 5.5 11.2": ["compulsories"], "11.1 13.9 8.2": ["rove"], "8.9 17.7 17.1": ["mockingbird"], "3.5 0.3 10.0": ["coiffure"], "-2.9 5.2 11.1": ["bachata"], "-11.2 24.8 1.4": ["impeachable"], "5.2 10.4 5.5": ["heeling"], "16.7 14.0 4.2": ["backlashes"], "-2.7 3.3 14.8": ["mantels"], "3.0 8.3 11.7": ["soothingly"], "-6.4 2.7 7.7": ["modulars"], "5.5 10.9 5.3": ["righthand"], "7.8 5.7 12.9": ["andrew"], "0.4 9.5 3.2": ["transliteration"], "13.9 3.3 9.7": ["clotted"], "11.8 5.0 4.0": ["freakout"], "0.7 4.5 10.2": ["arsenopyrite"], "3.7 14.0 9.4": ["climatological"], "2.6 6.6 11.1": ["kar"], "2.8 10.7 6.6": ["censorious"], "8.3 0.0 39.8": ["chive"], "3.4 6.8 17.9": ["caramelize"], "4.3 9.0 8.4": ["tangos"], "19.8 15.6 26.3": ["kingfisher"], "6.2 8.6 12.2": ["betwixt"], "5.6 10.5 11.3": ["licentious"], "15.0 7.9 4.7": ["twirlers"], "-8.0 5.6 14.5": ["cellulitis"], "-4.3 14.1 8.1": ["sportbike"], "-2.4 4.5 13.6": ["outro"], "8.6 14.2 10.1": ["eyewall"], "2.3 9.7 9.7": ["thet"], "14.5 11.6 6.4": ["blonds"], "23.4 18.4 21.0": ["booger"], "-0.8 19.7 -6.3": ["deniability"], "17.8 2.9 17.0": ["waterbed"], "4.0 -0.9 12.6": ["mary"], "-0.6 0.3 2.9": ["totted"], "-3.2 10.8 4.5": ["degradations"], "-2.4 3.6 22.1": ["strychnine"], "3.3 9.9 33.5": ["quails"], "0.8 11.7 1.9": ["outpoint"], "11.7 12.9 10.8": ["nuzzle"], "2.4 4.2 9.6": ["ayes"], "17.9 27.6 4.4": ["stormtroopers"], "4.0 21.1 24.1": ["hummers"], "-7.6 -5.8 7.4": ["carbamazepine"], "6.7 3.9 7.6": ["gymkhana"], "8.3 9.9 4.2": ["distrib"], "14.1 10.7 10.2": ["drudge"], "3.4 9.4 14.7": ["kneaded"], "-4.8 2.6 11.0": ["abv"], "7.1 8.7 23.3": ["scamp"], "4.5 18.5 17.7": ["fistic"], "-3.1 5.8 25.6": ["taxidermists"], "-5.8 8.6 -0.1": ["intelligibility"], "8.7 5.3 9.8": ["arcana"], "-5.9 1.9 -0.7": ["subjudice"], "9.3 -1.2 12.1": ["casa"], "3.4 22.8 14.0": ["prowlers"], "25.9 10.5 23.9": ["dinos"], "5.6 24.7 5.1": ["militarists"], "18.2 0.1 4.2": ["contruction"], "13.7 -4.2 19.8": ["boston"], "4.9 7.5 8.0": ["starkness"], "5.5 -0.5 12.4": ["patacas"], "11.7 13.0 10.6": ["hovels"], "0.1 14.5 10.3": ["clime"], "5.1 9.7 46.1": ["molluscs"], "1.2 8.0 12.7": ["hols"], "0.8 3.4 5.8": ["likley"], "9.9 6.3 5.8": ["tabulates"], "-5.4 10.3 10.7": ["heme"], "1.7 22.7 7.4": ["goads"], "4.8 8.0 4.3": ["wherefores"], "-0.9 7.6 1.2": ["abd"], "4.3 15.0 6.6": ["multipolar"], "-3.1 8.4 0.6": ["olim"], "-6.5 12.3 11.4": ["mucosa"], "7.4 10.8 -1.6": ["mnemonic"], "-0.1 15.0 1.1": ["harrassing"], "-6.0 15.5 -1.9": ["assessees"], "14.2 15.9 15.6": ["danged"], "7.1 10.1 10.3": ["ron"], "10.3 11.5 -6.2": ["noiseless"], "4.1 4.5 8.8": ["soooooo"], "17.1 8.5 6.9": ["flowchart"], "1.5 -2.9 10.8": ["chez"], "11.4 14.6 3.1": ["iconoclasts"], "-2.1 11.0 3.9": ["bazar"], "-4.1 15.5 17.1": ["aikido"], "12.8 0.0 5.0": ["jangled"], "3.2 14.6 2.8": ["reciever"], "9.5 1.5 3.3": ["pecent"], "7.8 14.7 2.6": ["oppressively"], "2.7 9.7 -0.3": ["unarguable"], "9.8 10.9 8.4": ["aborts"], "3.4 10.0 10.7": ["mouthguard"], "8.6 3.1 33.5": ["orzo"], "8.4 9.6 5.0": ["multisensory"], "1.2 1.8 8.9": ["colorants"], "10.8 10.3 10.2": ["clobbers"], "-1.9 8.2 7.1": ["differentially"], "-11.3 4.8 1.1": ["myelofibrosis"], "16.3 12.4 5.9": ["zit"], "-2.1 -2.8 5.9": ["microbus"], "-0.3 6.7 5.8": ["outpitching"], "4.5 21.1 0.1": ["canards"], "8.5 8.2 24.0": ["balsam"], "-5.4 9.5 1.5": ["essayists"], "2.0 7.1 9.6": ["underdressed"], "3.9 14.3 8.6": ["scrumming"], "-7.0 -1.0 -0.1": ["sophmore"], "-1.2 13.0 16.0": ["microclimates"], "18.7 2.7 16.4": ["junks"], "-2.7 12.6 11.0": ["perturbation"], "9.0 8.9 12.3": ["robert"], "-2.0 -2.6 -3.3": ["multilingualism"], "-3.2 26.8 2.4": ["delegitimization"], "7.5 14.8 6.1": ["muffling"], "-6.8 25.9 -0.7": ["warfront"], "8.7 31.2 9.9": ["villian"], "10.3 12.0 19.4": ["greenie"], "5.0 19.1 15.2": ["powerslam"], "-0.9 2.3 14.3": ["granites"], "12.7 13.7 2.8": ["superstate"], "-4.2 19.5 10.2": ["conjuncture"], "5.8 3.8 9.5": ["doco"], "-7.8 6.5 5.9": ["temperamentally"], "21.6 4.2 13.6": ["perspex"], "12.9 6.1 1.0": ["suchlike"], "8.6 3.3 16.0": ["buckskin", "frieght"], "-4.2 6.4 11.1": ["clubfoot"], "6.5 8.2 23.1": ["skillets"], "9.0 9.4 14.6": ["bonobo"], "-4.6 13.7 5.2": ["visibilities"], "-1.2 4.0 8.9": ["thermoforming"], "17.3 5.1 1.8": ["twinkled"], "11.4 26.6 10.5": ["mortally"], "17.1 10.6 12.2": ["sandboxes"], "-6.0 10.8 8.2": ["elim"], "-1.0 9.4 11.5": ["whitelisting"], "-3.4 1.9 4.5": ["gherao"], "6.9 1.5 15.3": ["clothespins"], "0.4 -1.3 11.7": ["breastmilk"], "10.2 4.5 8.0": ["relist"], "-1.0 13.5 8.1": ["racialized"], "-1.0 10.0 4.8": ["surmising"], "0.6 3.0 12.6": ["brogues"], "-5.4 12.0 3.0": ["continuations"], "1.9 9.5 0.2": ["nanostructured"], "13.6 -6.5 18.6": ["terrazzo"], "2.4 10.3 26.7": ["creole"], "-3.4 12.8 29.5": ["caddis"], "-1.6 5.8 2.5": ["digressed"], "-7.6 0.2 4.2": ["outkicked"], "-5.6 0.3 2.7": ["propoxyphene"], "-3.5 7.0 10.4": ["airguns"], "2.9 21.5 0.9": ["atomized"], "12.1 8.2 -2.2": ["expansiveness"], "-9.6 5.3 5.7": ["rifampin"], "8.2 0.5 6.9": ["warbled"], "4.0 6.3 -1.8": ["nonwoven"], "-8.5 5.0 10.5": ["embellishes"], "-1.3 9.6 27.8": ["bromeliads"], "4.4 3.2 3.9": ["brough"], "12.3 12.7 6.2": ["huggable"], "0.5 4.9 -2.2": ["aped"], "8.4 25.6 7.5": ["salvoes"], "9.7 8.5 4.3": ["segregates"], "10.0 0.3 -9.5": ["theworld"], "3.9 -1.8 9.6": ["dep"], "9.0 6.9 8.3": ["dollhouses"], "-0.4 24.0 8.8": ["miscalculate"], "9.6 17.4 19.5": ["biter"], "0.0 15.0 12.8": ["roto"], "15.0 7.1 2.4": ["sackcloth"], "-9.5 1.7 10.3": ["camisoles"], "12.9 21.4 19.5": ["icily"], "6.9 7.7 14.1": ["clamors"], "11.1 -0.6 11.9": ["udders"], "11.9 12.5 6.2": ["boycotters"], "5.8 23.4 2.7": ["frenemies"], "6.0 14.7 9.3": ["convective"], "8.8 12.9 7.3": ["adoringly"], "8.1 10.9 7.4": ["magnanimously"], "-1.3 12.7 5.4": ["overshoots"], "3.5 10.5 14.8": ["horserace"], "3.1 4.1 11.0": ["handcraft"], "4.2 12.2 11.7": ["caricaturist"], "0.7 15.4 2.6": ["disinflationary"], "-2.4 -1.6 0.9": ["req"], "-3.8 2.5 -1.8": ["misappropriations"], "2.9 -3.0 5.5": ["ella"], "2.6 -2.3 2.0": ["petajoules"], "1.7 4.4 6.0": ["counteroffers"], "-1.6 13.0 3.8": ["subsonic"], "11.4 13.8 16.2": ["voyagers"], "9.4 9.1 17.6": ["mooch"], "-2.2 4.1 10.2": ["sebum"], "1.0 5.7 11.8": ["toke"], "0.5 20.1 4.0": ["tensing"], "-7.2 12.6 18.2": ["grappa"], "16.9 11.0 0.8": ["transfixing"], "-9.8 4.7 -0.1": ["pastoring"], "3.6 14.8 12.6": ["misanthropy"], "11.7 13.4 9.7": ["contortion"], "27.9 4.6 9.9": ["astronomic"], "2.6 14.2 6.0": ["condescend"], "1.1 5.6 26.3": ["juiciness"], "8.5 7.7 8.2": ["calorific"], "-2.3 5.9 7.6": ["steeplechaser"], "-0.8 19.3 3.0": ["exalts"], "11.0 4.3 2.9": ["soldout"], "13.4 17.4 6.4": ["covetous"], "-4.2 4.8 -2.8": ["assignees"], "6.6 5.0 8.0": ["mews"], "7.1 10.7 7.0": ["pigsty"], "-1.8 -0.5 10.7": ["cst"], "1.9 -0.1 17.4": ["pag"], "-12.3 12.4 5.7": ["seniormost"], "0.7 9.5 26.4": ["hollies"], "2.1 3.8 -1.8": ["rightsholders"], "21.8 9.1 22.8": ["florescent"], "-3.8 12.9 13.8": ["underfund"], "10.6 16.7 8.4": ["blackmailers"], "1.1 12.5 5.9": ["unconstructive"], "7.6 12.5 12.1": ["vane"], "1.7 14.7 14.2": ["antivenin"], "13.7 16.6 15.7": ["superplex"], "4.0 8.6 6.1": ["thrashings"], "-5.7 8.1 0.4": ["psychopathy"], "4.3 17.7 12.0": ["reprobate"], "-3.8 1.7 -1.9": ["ester"], "3.5 5.8 -3.8": ["recondition"], "8.1 8.5 -1.7": ["pertinence"], "8.6 5.5 17.3": ["subsalt"], "6.5 9.3 6.8": ["cajoles"], "0.6 8.8 6.9": ["dumpsites", "duologue"], "11.3 -0.4 9.1": ["livening"], "20.4 0.5 12.5": ["contortionists"], "8.6 -0.2 13.5": ["megaproject"], "19.4 13.6 11.9": ["womankind"], "-3.5 13.2 1.7": ["contiguity"], "11.9 26.9 11.1": ["unmanly"], "7.5 2.6 2.6": ["wayfinding"], "6.5 -2.1 4.5": ["coater"], "-6.1 6.9 18.2": ["varicella"], "5.1 3.2 7.6": ["refits"], "4.6 14.2 15.3": ["repugnance"], "-5.7 11.6 5.9": ["victimizes"], "6.2 12.3 11.2": ["castled"], "-8.1 4.6 3.7": ["reinterpretations"], "13.1 14.3 16.6": ["codger"], "3.4 7.6 3.0": ["desparate"], "0.7 0.6 4.6": ["lavishes"], "-1.9 16.5 -4.9": ["misguiding"], "1.6 32.9 14.7": ["frag"], "5.9 12.8 19.7": ["crosscut"], "10.8 14.8 10.7": ["oafish"], "18.0 0.9 13.5": ["digi"], "14.5 6.1 27.2": ["hotpot"], "-1.7 5.0 12.0": ["inseminated"], "15.0 24.0 10.9": ["playfield"], "5.0 -3.6 13.0": ["skimpier"], "4.8 9.8 2.5": ["igniter"], "3.4 0.7 6.3": ["pottering"], "8.1 -3.0 6.4": ["unsponsored"], "4.8 7.4 5.0": ["aus"], "4.1 0.8 14.1": ["bustiers"], "10.1 7.3 -5.1": ["aquired"], "-0.2 7.0 10.9": ["repowering"], "6.7 11.0 9.8": ["nowt"], "6.8 17.5 1.8": ["frontiersman"], "14.3 4.4 5.7": ["unprecendented"], "2.2 14.7 5.3": ["assignation"], "3.8 2.2 10.5": ["nba"], "-0.3 1.1 12.7": ["roughage"], "13.1 14.0 9.2": ["crapper"], "6.8 11.7 -1.2": ["exclusiveness"], "-14.1 4.7 9.3": ["feticide"], "4.8 4.8 17.0": ["loafer"], "2.2 6.2 5.9": ["unflustered"], "-6.2 1.6 3.6": ["laned"], "7.4 -2.9 -5.3": ["pathbreaking"], "6.3 16.5 15.9": ["matey"], "7.3 28.4 5.8": ["idolatrous"], "9.1 4.6 13.6": ["tonite"], "-1.8 1.4 1.0": ["mboe"], "7.1 22.1 16.0": ["uncomprehending"], "9.8 9.6 5.5": ["addictiveness"], "16.9 12.5 21.0": ["outcroppings"], "-4.2 11.9 -2.2": ["voluntarism"], "9.8 6.7 0.7": ["alterative"], "1.9 0.4 3.8": ["familys"], "-0.5 2.8 10.1": ["decaffeinated"], "9.6 7.3 -1.6": ["vac"], "16.4 19.6 2.6": ["steeling"], "14.4 11.1 13.5": ["thrashers"], "14.8 9.6 31.7": ["wren"], "-1.1 12.5 29.9": ["daylily"], "-1.2 3.2 22.0": ["paan"], "-2.8 9.9 0.5": ["phonecall"], "2.0 18.6 16.1": ["harrier"], "4.2 -1.5 33.6": ["queso"], "-3.4 0.9 1.5": ["paydown"], "11.3 10.6 6.7": ["continous"], "5.2 21.9 6.5": ["airdropped"], "-4.6 2.0 4.8": ["heritability"], "-2.9 8.1 -1.4": ["verbalized"], "6.7 14.2 8.5": ["impermanent"], "0.4 8.9 -0.5": ["reacquiring"], "4.8 -4.9 19.5": ["kina"], "0.1 2.8 29.3": ["boatbuilding"], "5.6 3.8 9.4": ["infectiously"], "10.9 8.6 11.8": ["nuzzled"], "3.0 6.6 7.6": ["prebiotic"], "-2.7 8.2 -0.6": ["prefacing"], "8.1 0.5 12.1": ["paleontological"], "18.0 21.0 18.7": ["lances"], "10.4 12.0 -1.1": ["fulminating"], "4.0 7.5 -1.6": ["prototyped"], "22.2 6.9 6.0": ["shiniest"], "-0.7 1.0 3.6": ["polyphony"], "1.9 12.0 29.0": ["overcooking"], "0.4 6.6 7.1": ["virtualizes"], "2.9 10.6 17.1": ["wormwood"], "12.6 4.5 7.2": ["mastheads"], "9.4 6.1 4.3": ["knapsacks"], "11.2 11.3 9.9": ["stagnancy"], "5.7 12.4 6.6": ["allergenic"], "10.6 6.0 3.4": ["teenybopper"], "11.1 11.4 20.2": ["petunia"], "9.6 13.7 7.4": ["millenia"], "3.7 -0.8 7.8": ["druggy"], "3.3 10.4 39.8": ["morel"], "8.7 10.9 10.3": ["pickpocketing"], "-0.1 1.4 1.2": ["timeously"], "14.6 12.9 7.7": ["panted"], "4.6 5.8 13.4": ["casualization"], "4.1 8.0 11.1": ["dyspeptic"], "-2.5 15.8 5.9": ["oxidizer"], "4.6 12.9 3.4": ["clannish"], "4.0 5.5 8.7": ["anorexics"], "-5.6 2.9 1.3": ["hereunder"], "4.1 9.0 11.1": ["storekeepers"], "9.4 10.2 4.8": ["repositions"], "1.7 0.5 12.9": ["collies"], "-5.4 5.8 4.2": ["franking"], "-0.3 8.4 17.6": ["bloomer"], "0.7 13.2 13.7": ["heartiest"], "5.2 10.6 10.9": ["dipole"], "4.6 11.5 28.5": ["outrigger"], "6.3 -6.4 6.2": ["takeup"], "4.4 17.7 3.6": ["refuseniks"], "-5.2 2.2 -0.1": ["ev"], "6.0 21.2 6.9": ["guessers"], "10.3 9.1 -4.3": ["advancer"], "-1.4 1.7 12.8": ["boardinghouse"], "10.1 11.4 5.0": ["tromp"], "27.9 11.5 0.8": ["megastores"], "5.7 12.5 6.8": ["bigamist"], "0.4 0.4 6.4": ["rectifiers"], "14.9 3.3 4.3": ["mindblowing"], "9.5 9.4 17.4": ["galoshes"], "4.8 -3.0 9.7": ["interstitials"], "1.9 -2.7 11.3": ["gussets"], "0.1 8.8 2.0": ["dater"], "10.5 4.1 18.8": ["whitened"], "4.0 17.1 5.5": ["entente"], "10.4 13.9 -0.4": ["embarrasing"], "0.6 14.8 7.1": ["debilitation"], "4.2 7.2 5.2": ["ruder"], "2.9 10.7 14.8": ["courtesans"], "3.2 11.7 8.0": ["nanorods"], "3.3 8.3 14.1": ["bellybutton"], "6.5 2.3 8.2": ["urbanity"], "-0.2 10.9 4.7": ["cuffing"], "1.7 10.8 3.5": ["solipsistic"], "3.4 3.2 5.1": ["armer"], "11.1 13.3 11.5": ["uncreative"], "12.3 10.6 4.7": ["greenside"], "3.1 8.6 20.9": ["pungency"], "1.7 16.5 11.3": ["undrilled"], "-0.8 12.8 14.0": ["adages"], "-9.8 7.5 0.2": ["indentify"], "-4.4 -4.0 16.0": ["guar"], "1.9 14.7 13.1": ["solicitude"], "-0.9 10.9 12.4": ["polymerase"], "10.3 13.5 12.1": ["reemerging"], "-1.1 2.0 -2.2": ["earnout"], "1.6 3.7 7.6": ["decanting"], "-5.9 12.3 16.2": ["noncritical"], "0.4 15.2 12.6": ["abutter"], "-5.2 3.7 8.2": ["rehomed"], "12.6 37.1 16.3": ["mechs"], "7.9 31.6 10.4": ["deceiver"], "3.8 7.6 13.2": ["integrin"], "5.0 6.6 9.2": ["expander"], "21.5 -3.2 4.9": ["festoon"], "10.9 11.7 18.3": ["buckeye"], "5.6 7.6 13.8": ["flatland"], "10.0 10.7 5.4": ["jailbirds"], "2.5 7.0 8.4": ["pontiffs"], "-2.6 32.0 0.3": ["rearmed"], "10.5 4.3 5.0": ["savannas"], "6.0 5.1 14.6": ["lippy"], "2.4 4.1 12.6": ["glaciation"], "-0.6 -3.1 0.5": ["fiscals"], "5.0 22.8 8.1": ["psychically"], "1.1 6.6 3.6": ["unwatched"], "9.5 16.1 4.0": ["imbecilic"], "10.7 7.3 10.0": ["arbors"], "-1.1 1.1 6.1": ["nonregulated"], "11.5 -0.0 19.0": ["fuschia"], "5.0 0.1 3.8": ["sloppier"], "18.8 6.8 8.5": ["pharmas"], "0.4 4.2 2.9": ["defeased"], "-6.8 5.0 24.4": ["moong"], "-7.2 -5.6 6.7": ["dysphagia"], "5.2 31.6 9.5": ["wargames"], "3.7 4.0 11.2": ["overfill"], "4.9 6.6 26.9": ["civets"], "1.8 -3.7 -2.8": ["electrocardiograms"], "11.0 12.4 8.7": ["dancin"], "7.0 6.4 -1.7": ["cooperations"], "3.8 5.9 14.7": ["minks"], "0.2 12.9 8.0": ["completly"], "9.9 21.5 11.6": ["teleported"], "9.7 1.5 8.1": ["talkfest"], "3.4 6.9 6.7": ["imprudence"], "24.7 9.5 8.7": ["glassmaker"], "8.6 15.0 9.6": ["unfathomably"], "11.6 7.0 11.5": ["guffawing"], "5.1 11.1 4.7": ["contaminations"], "5.8 2.8 13.1": ["jfr", "monet"], "-2.8 2.8 5.5": ["sarod"], "1.8 6.8 8.1": ["possibilty"], "9.1 6.2 15.7": ["selldown"], "1.4 17.7 16.0": ["underboss"], "4.3 11.0 20.9": ["verbena"], "5.3 -5.9 7.6": ["weekender"], "-5.0 4.8 6.3": ["benchers"], "3.1 18.2 9.4": ["civilize"], "-4.1 3.7 3.4": ["croup"], "-0.7 11.5 10.2": ["antidrug"], "28.6 15.0 8.5": ["hugest"], "7.9 22.1 15.4": ["statists"], "9.9 2.8 18.6": ["chihuahuas"], "-2.9 6.4 0.5": ["chartbuster"], "-4.2 5.9 7.9": ["hardbacks"], "12.4 9.7 8.6": ["acme"], "4.4 11.6 6.8": ["aversive"], "12.1 -1.1 4.4": ["sta"], "-2.1 4.8 12.3": ["peatland"], "7.7 2.8 10.5": ["combinatorial"], "4.7 11.9 41.8": ["pinfish"], "-1.0 9.3 8.6": ["ali"], "11.8 19.4 14.1": ["pillbox"], "8.6 10.6 16.6": ["schistosomiasis"], "8.0 3.6 7.2": ["coexists"], "0.1 9.3 -3.9": ["pseudonymous"], "7.6 11.0 4.7": ["retching"], "-3.5 -3.9 2.3": ["telecare"], "5.3 -1.6 6.4": ["io"], "3.0 4.3 12.3": ["dy"], "7.8 4.6 20.9": ["cockatoos"], "-4.7 8.9 -0.4": ["reeducation"], "4.3 10.1 4.4": ["comicbook"], "3.3 13.8 12.6": ["unburied"], "-5.2 5.9 8.7": ["ard"], "5.1 4.7 17.1": ["haberdashery"], "12.1 15.5 10.6": ["imponderable"], "-0.1 3.6 45.5": ["perlemoen"], "-4.0 -0.4 17.1": ["pickleball"], "8.4 13.0 2.8": ["warred"], "-1.0 4.7 9.9": ["sphalerite"], "3.6 -3.4 2.8": ["diaphragms"], "2.3 3.0 -1.0": ["bei"], "-0.7 9.2 27.8": ["bighorn"], "2.1 13.7 8.0": ["alkaloids"], "19.8 4.1 4.0": ["trademarking"], "12.2 13.7 8.2": ["loudmouths"], "7.4 9.5 3.6": ["toweling"], "-1.1 16.7 10.4": ["balancer"], "-5.5 -9.1 -3.5": ["parttime"], "5.4 -9.9 10.8": ["brisker"], "-0.0 -2.3 6.1": ["chorister"], "5.8 4.0 15.4": ["congeal"], "-9.2 9.4 6.4": ["agriculturist"], "13.0 3.0 10.0": ["petanque"], "4.7 13.3 7.8": ["esthete"], "9.1 15.3 10.8": ["enigmatically"], "-0.0 4.6 6.4": ["murine"], "3.0 1.9 24.1": ["amaranth"], "5.9 7.7 4.8": ["sleepwalked"], "2.4 11.2 0.9": ["transportations"], "23.2 3.8 21.9": ["squiggle"], "-2.3 11.8 21.5": ["taxa"], "2.6 -0.3 2.6": ["biographic"], "-1.4 6.1 13.4": ["ferments"], "19.3 15.4 17.5": ["weenies"], "-5.9 6.5 5.2": ["dera"], "-3.7 15.7 23.4": ["muzzleloaders"], "8.2 13.3 -0.9": ["commissar"], "2.9 19.8 3.1": ["heresies"], "8.0 10.6 8.6": ["chaise"], "6.1 3.4 2.8": ["viva"], "10.2 6.3 -6.0": ["digitizes"], "-10.0 5.4 -1.7": ["candidatures"], "13.9 14.0 9.5": ["killjoys"], "-3.0 3.9 1.0": ["freethinking"], "27.1 9.4 18.7": ["caldron"], "-2.0 14.1 -0.1": ["hooding"], "10.8 11.1 -4.9": ["situating"], "-0.5 0.3 0.8": ["sheetfed"], "2.8 3.3 -4.5": ["custodianship"], "0.8 6.2 9.8": ["speakeasies"], "2.4 8.5 4.8": ["niqabs"], "13.8 4.0 4.4": ["jettisons"], "20.4 11.9 12.3": ["meister"], "19.2 6.5 6.0": ["chevron"], "9.4 12.6 5.0": ["nth"], "17.5 0.7 1.5": ["cobranded"], "3.1 13.0 4.2": ["disillusioning"], "1.8 7.3 11.7": ["heatsinks"], "4.1 13.1 3.0": ["deification"], "-8.0 9.8 12.3": ["accessions"], "-0.2 10.8 12.9": ["cornerman"], "14.1 11.8 10.8": ["counterweights"], "-11.6 -1.7 2.4": ["neurotoxicity"], "12.4 1.9 -0.5": ["hasbeen"], "0.4 4.1 5.9": ["mayoress"], "-3.9 9.5 5.9": ["portraitist"], "-4.6 27.4 6.8": ["mortared"], "0.7 14.2 11.7": ["impertinence"], "4.3 10.7 2.3": ["undersell"], "3.7 -1.1 8.3": ["dippy"], "9.4 12.1 5.1": ["gutsiest"], "10.0 5.5 11.4": ["agoraphobic"], "11.6 10.8 9.4": ["cheapskates"], "-3.9 13.7 7.8": ["eosinophils"], "2.9 24.1 9.7": ["muggles"], "12.0 21.6 12.5": ["harlot"], "12.6 6.2 25.0": ["goslings"], "1.7 1.7 14.1": ["hsiung"], "5.6 21.3 1.3": ["servicewoman"], "13.4 13.2 10.9": ["uhh"], "16.3 13.6 23.0": ["multitudinous"], "4.5 28.6 1.7": ["insurgence"], "5.7 2.2 3.6": ["unpacks"], "-1.5 13.4 11.3": ["trapshooting"], "14.8 21.7 7.7": ["cooties"], "11.0 4.1 0.3": ["ove"], "6.7 7.9 16.0": ["cig"], "13.8 1.9 13.7": ["skinniest"], "2.4 22.1 7.6": ["fecklessness"], "-6.4 4.6 9.4": ["reposting"], "-1.8 10.3 4.2": ["timestamp"], "5.6 24.9 5.6": ["diabolically"], "7.0 17.1 12.0": ["deviously"], "16.2 3.8 -0.5": ["snoozed"], "4.4 10.1 11.8": ["spammy"], "3.0 13.4 0.4": ["gps"], "-0.9 4.5 -4.3": ["wel"], "1.1 19.4 11.0": ["multitasker"], "0.4 3.2 10.0": ["pneumococcal"], "6.7 9.0 11.8": ["consignee"], "4.8 9.2 6.2": ["simplifications"], "0.5 17.8 11.7": ["hurtin"], "-0.8 2.4 6.9": ["wks"], "11.6 8.8 -2.6": ["internationalizing"], "-3.1 -0.3 -2.9": ["ferumoxytol"], "1.2 8.7 20.6": ["tandoor"], "8.3 17.5 1.0": ["vilifies"], "9.7 3.6 9.9": ["fez"], "5.9 7.2 18.1": ["raceways"], "10.9 7.4 12.7": ["lovelier"], "-0.1 11.7 24.3": ["aster"], "3.4 10.0 6.1": ["waywardness"], "3.2 8.2 -2.3": ["remonstrating"], "10.3 -4.8 8.1": ["phil"], "-9.3 5.7 0.6": ["rescreened"], "7.2 5.2 3.0": ["excitment"], "5.6 9.4 6.9": ["socializes"], "2.8 13.7 1.4": ["overexertion"], "15.2 2.7 28.0": ["clamshells"], "4.5 23.8 13.4": ["penetrators"], "-14.2 11.6 8.3": ["noncriminal"], "-2.3 5.4 -0.8": ["conflates"], "-4.0 0.9 4.0": ["daclizumab"], "9.5 0.6 20.7": ["broomball"], "-8.9 2.3 2.2": ["titrated"], "7.7 14.2 -1.4": ["purchasable"], "14.4 0.8 6.9": ["totter"], "3.4 -3.0 12.3": ["megs"], "9.9 7.0 7.1": ["lasered"], "-2.2 0.7 12.6": ["fado"], "13.2 12.4 2.0": ["everthing"], "14.2 -0.4 14.7": ["handpainted"], "11.9 25.6 3.7": ["supermen"], "12.7 6.7 5.9": ["sheered"], "0.6 1.7 11.0": ["aughts"], "10.3 23.1 11.1": ["mote"], "6.6 10.2 9.8": ["nonconformity"], "-5.3 5.6 35.1": ["broths"], "7.3 3.6 8.8": ["mais"], "-0.9 5.9 8.6": ["ultraportables"], "15.5 10.6 15.3": ["zits"], "9.2 11.8 28.7": ["swimbaits"], "-4.7 3.4 1.1": ["joinder"], "-4.1 2.3 12.0": ["telomere"], "10.0 8.3 15.9": ["shiftless"], "0.4 8.6 1.5": ["unavailing"], "9.3 4.6 1.5": ["mollifying"], "-2.1 14.0 7.1": ["jayvees"], "3.7 -0.9 -0.0": ["orthobiologics"], "14.2 6.9 3.2": ["embroiling"], "9.9 -0.6 -1.2": ["mooting"], "-6.3 10.4 7.3": ["wheelspin"], "5.4 8.8 14.1": ["godchildren"], "15.0 10.8 12.7": ["placidly", "plastically"], "19.9 18.5 19.8": ["impale"], "3.5 1.3 2.7": ["jazzman"], "8.3 16.9 12.1": ["clods"], "6.3 8.0 -0.8": ["combusted"], "-4.6 1.9 8.6": ["haloperidol"], "-1.8 5.3 26.0": ["flavoursome"], "6.1 36.9 7.4": ["totalitarians"], "6.1 6.1 2.1": ["anyday"], "2.6 14.0 5.2": ["snitched"], "-6.8 6.6 8.9": ["quintiles"], "7.1 11.6 9.5": ["waterhole"], "8.8 3.9 3.3": ["dissapointing"], "-8.0 7.5 5.6": ["improvisatory"], "5.0 -4.0 7.4": ["fil"], "-4.1 5.5 8.2": ["mezuzah"], "13.5 8.4 10.2": ["writhes"], "37.2 13.3 20.4": ["pterodactyl"], "-2.6 7.6 10.5": ["stomachaches"], "-2.3 10.3 9.3": ["hamstringing"], "7.6 20.0 7.6": ["perforate"], "3.8 12.8 10.0": ["epaulets"], "-0.6 13.8 6.5": ["enunciating"], "12.0 15.8 9.9": ["stealers"], "5.2 -1.8 -0.6": ["delink"], "20.4 7.5 10.9": ["crazes"], "0.5 10.7 15.0": ["guesstimates"], "-1.1 8.5 -5.3": ["condoles"], "-2.3 3.5 2.6": ["deejaying"], "4.1 10.1 2.1": ["shamanism"], "-4.3 2.7 -1.7": ["neurostimulation"], "5.7 11.7 35.3": ["butternut"], "-8.6 3.6 8.4": ["natalizumab"], "12.1 5.3 0.3": ["lubricates"], "-3.8 7.8 9.2": ["fineness"], "2.0 3.1 10.3": ["torqued"], "8.4 -0.3 12.2": ["slipcover"], "-1.8 10.8 17.6": ["horseplayers"], "9.1 12.7 10.2": ["crassly"], "-1.3 6.0 5.4": ["grammars"], "-3.6 14.4 12.8": ["sabermetrics"], "5.7 5.5 21.0": ["tanner"], "-0.7 21.0 3.3": ["monotheistic"], "-0.9 -4.1 -4.4": ["pepped"], "-2.6 17.7 13.8": ["noncitizen"], "1.2 12.2 12.6": ["repatriates"], "-3.0 14.7 5.2": ["phosgene"], "0.8 21.0 4.7": ["aftermaths"], "1.2 3.7 5.4": ["sonorities"], "6.0 16.2 9.3": ["babying"], "-1.5 7.0 10.3": ["haplotype"], "-2.8 7.9 7.6": ["fluoridate"], "-3.2 10.8 18.4": ["hardscape"], "-4.9 5.5 1.7": ["misdiagnoses"], "8.9 15.4 30.2": ["chunking"], "-2.3 9.6 11.6": ["exasperate"], "6.9 -0.4 15.8": ["decker"], "13.6 16.3 0.6": ["defanged"], "-13.1 0.8 12.7": ["foaling"], "0.1 3.7 1.3": ["dissuades"], "6.2 -2.1 4.0": ["acc"], "2.1 -1.0 9.2": ["fussiness"], "-10.1 14.9 1.4": ["encourager"], "19.2 7.1 10.7": ["undershot"], "-3.8 3.9 4.4": ["guidewire"], "10.2 16.7 8.0": ["swappers"], "15.4 -1.8 2.1": ["wended"], "-0.9 15.8 8.9": ["shiftiness"], "4.1 -5.2 9.6": ["nearside"], "5.5 -2.3 -1.9": ["vicepresident"], "10.0 11.3 7.7": ["graphed"], "2.3 29.7 10.8": ["fratricidal"], "4.8 5.1 3.7": ["grandaughter"], "-3.5 12.2 1.3": ["recuperative"], "5.5 17.2 8.4": ["obduracy"], "-0.6 17.0 2.3": ["predispositions"], "2.8 10.5 1.5": ["deprecated"], "0.4 4.8 6.2": ["farmout"], "11.6 3.9 34.4": ["croquettes"], "2.0 10.9 6.6": ["excitability"], "6.4 8.9 6.4": ["newsflash"], "16.9 3.3 20.6": ["licious"], "-2.5 14.7 2.9": ["oppurtunity"], "11.3 2.7 10.4": ["poshest"], "-1.8 7.0 13.4": ["breaststroker"], "2.9 4.1 10.8": ["bandwith"], "-2.0 14.3 11.9": ["cruiserweights"], "4.0 4.0 -8.8": ["spokeperson"], "14.0 6.4 15.5": ["dandies", "bidons"], "3.0 12.8 13.2": ["gabbro"], "13.3 7.8 9.4": ["apostrophes"], "-0.6 -0.2 -8.9": ["catalysed"], "5.8 18.4 12.0": ["supernaturally"], "20.1 3.4 14.6": ["palooza"], "0.8 1.2 11.1": ["erhu"], "1.4 9.7 9.0": ["agriculturalists"], "6.3 6.1 11.4": ["dices"], "7.2 9.0 7.0": ["implausibility"], "14.9 10.4 8.6": ["caroming"], "6.0 19.7 8.0": ["fainthearted"], "9.4 1.8 13.6": ["titbits"], "3.9 11.9 0.9": ["putatively"], "-2.6 7.6 -4.0": ["euronews"], "1.3 5.9 11.5": ["pissy"], "-14.4 5.1 3.5": ["prefaces"], "5.9 9.6 1.6": ["reducer"], "1.9 5.6 7.3": ["leaver"], "16.0 8.3 24.7": ["piggies"], "10.4 8.1 8.3": ["hydrostatic"], "-2.3 15.3 15.1": ["barca"], "4.2 32.1 3.7": ["defeatists"], "-3.1 10.3 4.5": ["regressions"], "4.0 12.8 8.5": ["cyberpunk"], "-0.1 9.4 5.0": ["couching"], "8.0 9.2 29.2": ["kraut"], "12.8 7.4 15.1": ["lovably"], "1.5 2.1 6.0": ["factsheet"], "11.3 13.6 19.7": ["meathead"], "5.4 6.4 9.2": ["aptamer"], "-2.8 1.3 0.5": ["firesuit"], "-10.3 3.3 7.8": ["merchandize"], "12.8 -1.3 13.0": ["shakin"], "7.2 -4.8 21.0": ["chapeau"], "8.2 5.3 -0.2": ["twitters"], "18.5 8.2 18.4": ["reindeers"], "17.9 3.2 -1.2": ["stretchable"], "3.8 12.3 2.4": ["phosphors"], "9.7 8.4 -0.9": ["miniaturize"], "-9.8 10.3 1.6": ["hyperhidrosis"], "11.8 9.6 26.4": ["skinless"], "4.4 7.3 11.3": ["gavels"], "5.0 12.3 17.5": ["volatiles"], "7.3 6.5 11.6": ["dumbfounding"], "0.7 19.5 7.3": ["unthinkingly"], "10.1 11.7 13.7": ["puzzlers"], "-7.7 12.4 5.3": ["analytes"], "3.5 5.3 19.9": ["blackcurrant"], "-2.6 16.0 6.3": ["moderns"], "-4.8 14.1 -2.5": ["eventhough"], "2.6 14.9 21.8": ["monohulls"], "13.2 -4.4 8.8": ["stackers"], "10.4 11.6 14.1": ["elixirs"], "15.0 11.7 3.1": ["satirically"], "-1.8 -1.8 14.2": ["calved"], "-2.4 -5.8 8.5": ["nonclinical"], "15.1 13.5 13.7": ["honeycombed"], "5.0 12.6 7.1": ["discolor"], "9.3 5.1 7.9": ["overallotment"], "16.4 8.9 11.2": ["thumper"], "-6.2 10.9 3.5": ["religous"], "13.2 11.0 20.5": ["curmudgeons"], "1.4 13.1 9.3": ["jokesters"], "2.1 13.2 5.8": ["assuredness"], "-0.2 7.5 11.6": ["epidermal"], "-1.1 2.5 16.0": ["nettops"], "9.6 11.5 15.3": ["stalagmites"], "13.2 7.8 10.5": ["gormless"], "14.8 1.6 20.4": ["candleholders"], "9.1 -3.5 -3.4": ["hotted"], "5.8 6.6 10.5": ["nightie"], "16.9 13.3 7.2": ["spillages"], "12.1 6.0 1.8": ["incongruities"], "7.0 -2.7 3.5": ["binged"], "3.8 4.3 9.5": ["pablum"], "-1.4 8.8 7.0": ["soffit"], "10.3 14.1 28.8": ["beachcombers"], "-8.9 10.0 0.5": ["instrumentally"], "1.0 11.0 3.7": ["homestands"], "-1.0 1.0 21.6": ["autograft"], "-1.1 11.9 7.9": ["motorman"], "-8.9 26.8 4.9": ["reconcilable"], "-7.9 10.1 11.0": ["lymphocyte"], "-1.0 8.8 8.6": ["liveability"], "5.4 10.2 23.7": ["sloops"], "14.6 15.2 9.2": ["boons"], "1.8 13.4 5.6": ["objectifying"], "8.3 10.4 0.0": ["hundredfold"], "-0.4 11.6 6.5": ["coyness"], "-5.1 4.9 7.6": ["parishwide"], "8.0 23.7 17.2": ["wussy"], "10.2 4.9 6.3": ["clowned"], "6.0 11.8 9.7": ["windbag"], "9.7 12.3 13.3": ["moneychangers"], "2.8 12.7 10.9": ["polymorphic"], "-0.8 6.1 6.9": ["toxoplasmosis"], "4.0 4.9 21.9": ["kate"], "8.8 14.9 3.1": ["reincarnate"], "3.5 10.7 8.3": ["bylanes"], "1.7 27.3 7.4": ["bellicosity"], "6.6 10.1 3.2": ["vaporizer"], "-7.2 11.9 6.0": ["basestation"], "-2.2 11.5 8.3": ["picocell"], "3.6 4.0 16.2": ["limerick"], "8.4 1.5 16.6": ["tweedy"], "1.8 8.2 18.9": ["mandible"], "5.8 4.9 -1.2": ["conceptualise"], "11.4 5.9 30.0": ["praline"], "-1.7 9.6 5.3": ["lucy"], "-0.6 3.0 5.8": ["shuteye"], "2.0 8.3 7.5": ["unredeemed"], "5.7 13.6 -1.4": ["foriegn"], "15.0 5.7 31.0": ["primrose"], "9.1 8.6 16.9": ["pidgin"], "-2.8 4.7 12.3": ["blastocyst"], "12.4 5.2 14.9": ["sci"], "-6.0 0.7 6.1": ["tunings"], "11.3 5.7 16.7": ["wala"], "-3.3 20.8 4.3": ["maliciousness"], "-3.7 13.3 3.0": ["downtimes"], "15.2 4.7 12.9": ["teepees"], "-0.1 -0.4 1.6": ["apperance"], "20.4 2.7 10.3": ["bonanzas"], "7.8 11.9 15.4": ["kismet"], "-2.3 -6.1 0.9": ["xylene"], "3.3 6.6 7.3": ["landholding"], "0.3 20.4 3.7": ["doglegs"], "2.9 12.2 8.9": ["extroverts"], "1.0 0.4 5.1": ["lipoprotein"], "1.5 4.2 13.1": ["brecciated"], "16.9 2.6 14.5": ["torpid"], "10.2 12.8 21.7": ["keels"], "10.6 6.3 28.9": ["stevedore"], "-2.8 -2.4 30.5": ["brined"], "0.8 7.2 9.3": ["freon"], "11.3 10.0 17.8": ["falconer"], "-0.2 4.8 6.3": ["intersperses"], "17.9 13.9 15.5": ["errr"], "1.2 -1.3 6.5": ["inulin"], "14.9 1.9 3.4": ["noticeboard"], "-5.7 4.5 -2.5": ["acheived"], "1.4 7.7 4.9": ["taxability"], "2.4 14.4 3.4": ["disproportion"], "0.7 17.9 3.5": ["mythologized"], "15.0 13.9 5.2": ["nonfunctioning"], "-2.8 3.6 16.1": ["jackups"], "-4.1 7.3 2.9": ["hummable"], "-1.5 2.3 -1.2": ["supercapacitors"], "7.1 22.4 9.0": ["hotkeys"], "-8.5 -2.2 9.4": ["chairwomen"], "3.2 6.5 38.6": ["tapenade"], "-1.8 -0.5 9.6": ["summered"], "8.1 6.5 5.2": ["prattling"], "11.4 17.5 11.7": ["glyphs"], "-2.3 20.4 4.4": ["ennobling"], "5.6 11.0 4.6": ["discomfited"], "17.0 26.1 7.4": ["lightsabers"], "1.7 6.7 13.4": ["steerage"], "-6.0 7.0 0.7": ["exchanger"], "9.8 9.0 5.1": ["huffs"], "10.8 1.8 19.0": ["woks"], "11.2 8.8 8.6": ["hydraulically"], "2.6 18.2 10.6": ["congressperson"], "3.3 -0.2 14.2": ["tum"], "8.5 1.0 10.3": ["eng"], "-4.6 2.0 10.2": ["autoharp"], "-2.6 6.6 17.4": ["mestizo"], "-0.2 5.1 5.3": ["naturist"], "-1.0 17.1 9.0": ["leftism"], "-4.9 17.1 7.4": ["subnet"], "-0.8 20.3 6.4": ["disbelieved"], "13.2 8.2 13.8": ["grifters"], "4.0 15.0 7.4": ["bullheaded"], "-1.3 20.2 8.5": ["warlordism"], "8.3 -5.6 3.9": ["spritely"], "2.4 5.4 -7.5": ["bloodstreams"], "8.1 4.2 21.5": ["gustatory"], "25.0 1.6 2.1": ["tieup"], "-0.4 4.4 2.2": ["podcaster"], "5.0 3.4 31.4": ["courgettes"], "14.5 15.7 3.3": ["superimposing"], "-1.0 11.0 9.6": ["backmarker"], "5.7 4.6 -1.3": ["werden"], "1.7 9.9 8.7": ["shtetl"], "0.3 8.7 10.8": ["intersectional"], "6.9 -4.0 6.2": ["laffer"], "-3.2 2.9 13.9": ["prasad"], "9.0 7.0 -1.1": ["dmg"], "20.3 11.2 16.5": ["gaily"], "-1.9 -3.2 3.8": ["gleans"], "1.1 12.2 4.9": ["corruptible"], "8.4 14.7 9.6": ["scifi"], "4.4 4.6 10.8": ["interconnector"], "-10.0 5.1 14.1": ["bourbons"], "8.7 14.1 24.4": ["druid"], "-3.9 6.9 2.5": ["bioequivalent"], "12.3 12.4 4.2": ["doorbells"], "5.9 9.0 4.5": ["nicety"], "0.9 5.3 0.6": ["parser"], "-6.6 5.9 6.6": ["telemovie"], "-10.7 7.6 -1.9": ["bronchiolitis"], "-5.0 12.1 9.9": ["duodenum"], "0.6 4.0 6.6": ["sitio"], "21.7 32.4 22.4": ["pincer"], "-7.7 14.1 3.5": ["hawkishness"], "22.2 -3.7 7.7": ["ofa"], "6.8 2.1 6.7": ["hep"], "2.1 2.0 5.1": ["heeler"], "-3.5 15.1 5.5": ["aquaplaning"], "7.6 8.6 7.3": ["squeegees"], "0.4 12.9 26.0": ["blanching"], "6.7 10.7 4.5": ["overfunded"], "-3.5 0.9 2.0": ["presidentship"], "9.8 15.1 -0.5": ["transmuted"], "1.3 32.3 1.7": ["counterrevolution"], "-2.1 -1.3 4.7": ["mgs"], "-1.7 20.9 9.8": ["indirection"], "-2.0 15.7 13.9": ["snakebites"], "-1.2 17.3 17.4": ["flus"], "8.9 17.5 18.4": ["mongrels"], "-0.2 12.1 5.9": ["influentials"], "4.3 11.5 -2.0": ["cumulated"], "1.3 2.9 10.5": ["tenderers"], "-0.9 19.3 4.0": ["misguide"], "0.3 14.7 -1.0": ["divined"], "1.4 -2.4 6.3": ["pedestrianization"], "-1.6 1.1 7.9": ["recompletions"], "2.5 5.6 39.5": ["porcini"], "-0.1 2.7 14.0": ["gwan"], "0.7 7.0 14.4": ["sulforaphane"], "7.8 4.5 12.3": ["gaits"], "10.2 12.0 11.4": ["scrunch"], "1.2 1.8 18.9": ["cheesemaking"], "3.2 7.7 19.5": ["busboys"], "-1.4 4.4 22.8": ["resto"], "13.8 1.3 11.8": ["ata"], "12.0 -3.4 1.2": ["superfund"], "-8.1 -0.5 -8.4": ["devotionals"], "-4.4 -0.3 -1.5": ["gpa"], "3.6 1.8 7.3": ["multitenant"], "-1.9 8.5 3.9": ["sensationalise"], "-4.6 8.0 22.6": ["toddy"], "1.5 12.0 -0.5": ["drubbings"], "-3.4 -3.6 14.4": ["lowfat"], "0.6 11.5 3.4": ["scatterbrained"], "14.1 8.8 8.4": ["tramlines"], "13.0 5.1 4.7": ["bldg"], "8.0 2.4 16.4": ["gams"], "1.5 5.3 15.3": ["blastocysts"], "11.7 8.3 5.0": ["sunshades"], "-8.0 -0.4 4.1": ["gynecologic"], "11.5 8.7 9.6": ["chancel"], "8.7 15.3 6.1": ["industrialise"], "2.3 15.9 18.4": ["bowman"], "18.8 15.8 17.8": ["daintily"], "-1.6 6.5 5.2": ["fissile"], "7.1 10.7 14.1": ["aerating"], "6.5 6.7 0.5": ["scienter"], "9.0 11.1 13.2": ["minx"], "-5.6 9.7 2.4": ["readjustments"], "6.4 9.7 7.9": ["pubcos"], "7.9 3.4 8.2": ["indelicate"], "1.1 22.5 4.1": ["polemicist"], "-4.6 16.6 8.8": ["theologies"], "7.3 11.7 8.8": ["blackmails"], "-7.5 -7.5 3.2": ["attn"], "1.4 7.5 10.3": ["sharable"], "0.4 3.3 6.5": ["flexo"], "2.3 10.1 30.5": ["dahlia"], "3.8 6.1 8.9": ["smelted"], "-2.9 8.6 4.1": ["retweeting"], "8.1 17.2 5.2": ["triangulated"], "-8.0 6.5 -3.0": ["nikah"], "0.7 12.1 11.9": ["superbikes"], "0.7 4.1 14.0": ["farriers"], "-5.4 5.1 12.5": ["undergrounding"], "1.2 -2.9 12.7": ["riper"], "11.4 4.2 3.1": ["videocassette"], "-0.9 10.2 17.7": ["repot"], "0.7 10.5 10.6": ["chortles"], "13.4 26.5 5.9": ["propoganda"], "5.1 -2.0 16.0": ["ruched"], "2.3 6.6 4.4": ["kopecks"], "2.9 7.9 7.8": ["formbook"], "5.5 15.6 12.2": ["bloops"], "9.3 9.7 4.4": ["curdle"], "15.7 6.4 19.8": ["snaffle"], "-7.7 1.7 2.0": ["erasures"], "0.8 5.5 8.4": ["goto"], "8.0 -0.1 16.0": ["chamois"], "4.5 5.2 5.9": ["solidification"], "6.1 8.4 23.2": ["tucker"], "19.9 9.2 21.8": ["huggers"], "-7.7 -4.6 -2.5": ["docketed"], "5.9 17.0 10.2": ["offed"], "5.1 7.8 11.4": ["windowing"], "-1.6 3.2 7.6": ["bitstream"], "-5.7 6.6 8.3": ["biotherapeutic"], "0.3 5.6 -1.1": ["specialisms"], "5.8 2.4 31.1": ["sheephead"], "5.2 16.9 6.3": ["agitates"], "21.5 9.6 17.9": ["shipload"], "5.3 11.8 8.4": ["pieties"], "12.3 4.1 13.4": ["highchair"], "9.7 -0.3 13.2": ["coked"], "-3.5 5.1 2.1": ["timespan"], "17.7 3.5 15.4": ["derricks"], "3.6 14.3 5.8": ["bleakly"], "17.5 5.2 20.0": ["horsehair"], "-4.2 2.3 14.6": ["magnums"], "0.8 11.4 7.2": ["immuno"], "-1.7 10.2 3.1": ["overvalue"], "-3.5 6.6 0.2": ["proposers"], "-1.6 3.1 8.3": ["fibrin"], "10.1 11.0 8.8": ["pompously"], "5.4 4.8 -0.7": ["externalizing"], "-3.1 1.2 10.2": ["halters"], "5.1 7.1 3.8": ["eurogroup"], "9.9 13.2 13.3": ["excreta"], "14.9 5.4 6.6": ["gurgles"], "4.2 13.3 8.0": ["shoud"], "3.3 12.5 11.6": ["chars"], "7.9 8.0 24.5": ["tuatara"], "12.4 25.8 11.6": ["poltergeist"], "3.7 -0.8 9.7": ["eisteddfod"], "6.9 5.6 3.6": ["waaay"], "6.8 6.6 1.0": ["enemas"], "-4.3 8.4 3.8": ["bootstrapping"], "-10.6 9.0 1.5": ["melphalan"], "-0.1 13.5 15.9": ["scorekeeping"], "3.0 6.5 12.5": ["libidos"], "-6.4 22.2 11.2": ["licit"], "-2.6 11.7 16.7": ["crier"], "-5.0 8.1 6.9": ["nonsexual"], "1.7 12.1 6.0": ["enduringly"], "9.8 4.8 11.7": ["popsters"], "4.2 24.3 16.5": ["groundstroke"], "-9.6 14.4 10.4": ["glioblastomas"], "4.3 16.8 20.7": ["headsail"], "-2.1 19.5 4.5": ["carbines"], "1.7 15.6 1.3": ["sidedness"], "12.5 14.1 10.1": ["booters"], "9.0 15.0 9.7": ["sourpuss"], "4.2 5.1 4.4": ["antidiscrimination"], "8.1 9.6 11.5": ["sparser", "grandpapa"], "7.6 -3.5 3.4": ["noncompete"], "-1.3 5.1 8.6": ["neocortex"], "-6.9 6.5 8.8": ["undervote"], "6.3 4.6 3.9": ["nondurables"], "15.8 3.3 9.6": ["clack"], "9.8 3.7 25.6": ["fajita"], "6.8 8.6 7.7": ["frack"], "11.8 1.6 7.1": ["crossbars"], "-5.1 -0.8 6.3": ["naturopathic"], "19.1 5.0 14.8": ["pompom"], "3.4 0.4 7.7": ["funicular"], "8.3 1.7 5.2": ["bioplastic"], "-0.9 3.5 10.9": ["auditioners"], "16.9 -5.0 16.8": ["perma"], "11.0 5.6 1.0": ["futurism"], "17.2 15.2 9.7": ["reanimated"], "-4.7 11.0 16.3": ["rhyolite"], "10.0 16.6 12.5": ["bullwhip"], "0.7 6.4 5.5": ["aneurism"], "8.9 0.8 7.3": ["nanofibers"], "6.9 7.7 31.2": ["canner"], "-0.8 19.6 6.2": ["toggled"], "-8.1 8.8 12.5": ["prorogue"], "2.4 -5.3 10.4": ["highlighters"], "3.5 11.6 4.1": ["bards"], "8.3 0.5 10.8": ["ohio"], "1.8 9.2 9.0": ["catchweight"], "-1.9 15.0 0.6": ["abettor"], "-2.4 13.9 -3.5": ["purifiers"], "-2.7 17.9 8.1": ["positionally"], "3.4 3.3 10.3": ["canasta"], "6.0 24.0 3.9": ["sadistically"], "13.0 16.9 11.3": ["antediluvian"], "-4.5 9.4 9.6": ["nonconfrontational"], "-4.4 2.6 7.3": ["isoforms"], "-3.1 11.1 7.7": ["poliomyelitis"], "-10.0 6.3 1.9": ["nonexempt"], "11.7 9.6 10.7": ["impracticality"], "7.9 15.8 8.6": ["punditocracy"], "-6.8 11.8 12.1": ["reportorial"], "-2.2 15.3 7.1": ["moralism"], "9.8 7.6 12.6": ["bluebloods"], "5.4 5.6 18.7": ["gutka"], "5.2 4.6 19.8": ["chad"], "-4.3 6.4 5.4": ["sumatriptan", "raina"], "2.7 9.2 4.2": ["carbons"], "13.7 2.8 10.8": ["hom"], "11.8 25.8 27.9": ["varmint"], "1.3 6.1 15.3": ["bal"], "13.9 3.6 2.0": ["cartwheeled"], "2.5 18.0 16.1": ["stovepipe"], "-0.4 11.2 3.7": ["compartmentalization"], "4.0 -0.9 3.9": ["underrepresentation"], "8.8 25.5 26.5": ["cutthroats"], "4.9 12.7 8.4": ["prudes"], "4.5 8.0 8.5": ["qua"], "2.2 7.6 3.1": ["unclogging"], "19.9 -1.8 18.9": ["bonbons"], "-7.6 1.7 1.1": ["naturopathy"], "1.1 2.5 4.0": ["dicier"], "1.8 5.8 14.2": ["incomers"], "5.7 20.4 7.8": ["dirtbag"], "-2.3 3.9 -1.6": ["reconfigurations"], "13.9 8.6 19.8": ["gibbon"], "12.6 -2.1 5.0": ["heiresses"], "-6.2 2.7 1.6": ["ondansetron"], "0.3 6.5 23.6": ["chitosan"], "-7.4 -1.0 1.3": ["wearability"], "17.8 12.3 11.3": ["vixens"], "3.7 4.6 37.1": ["fishpond"], "10.9 5.3 7.9": ["stepwise"], "10.8 24.3 4.5": ["cyberterrorism"], "10.0 8.5 14.7": ["beatbox"], "2.6 14.5 -0.7": ["anyones"], "10.0 5.7 4.7": ["anonymized"], "5.3 5.4 13.8": ["hua"], "15.0 19.4 8.4": ["geekiness"], "10.1 0.4 0.4": ["wellknown"], "5.9 27.7 3.2": ["resoluteness"], "-11.9 4.2 2.6": ["sertraline"], "5.7 3.8 21.0": ["mahouts"], "2.8 1.1 6.2": ["covetable"], "7.5 13.2 3.3": ["thirsts"], "2.1 2.9 -0.4": ["acceptor"], "-1.9 8.9 11.3": ["grandbabies"], "6.6 6.3 14.6": ["natgas", "kienet"], "3.2 0.8 17.0": ["eyelet"], "4.5 16.4 10.9": ["gruffly"], "2.3 10.1 5.5": ["pushbutton"], "0.2 15.3 9.6": ["retrogression"], "12.9 17.4 1.9": ["exulting"], "7.0 15.5 1.9": ["struggler"], "3.7 -2.9 20.4": ["linerboard"], "13.7 -3.1 12.4": ["spendy"], "4.5 1.4 3.2": ["stickhandled"], "21.5 7.4 15.7": ["skitter"], "5.6 9.3 1.3": ["mispronouncing"], "6.4 5.2 -0.8": ["hh"], "-4.1 22.5 -0.8": ["oppressions"], "-1.3 12.7 12.3": ["nondefense"], "4.1 21.6 9.7": ["counterproliferation"], "-0.6 -5.1 2.8": ["resealing"], "15.0 23.2 7.0": ["scenting"], "14.5 14.7 6.8": ["sunshade"], "7.1 -6.0 8.2": ["extendible"], "-7.1 8.7 8.3": ["noninterest"], "6.0 3.3 34.9": ["celeriac"], "-2.5 6.8 8.3": ["depletions"], "-0.7 8.7 5.7": ["carabinieri"], "1.9 4.3 9.1": ["operettas"], "-3.0 6.5 4.7": ["dicta"], "-7.3 8.4 21.8": ["bulgur"], "9.5 4.6 15.0": ["ringlets"], "13.8 8.1 19.7": ["crone"], "-15.1 6.7 6.6": ["chemoprevention"], "7.7 22.2 14.5": ["colonist"], "9.5 14.7 14.2": ["glade"], "2.2 17.1 9.5": ["emotes"], "10.9 4.7 3.2": ["sunroofs"], "-5.0 21.7 1.4": ["logisticians"], "1.2 4.8 26.5": ["astaxanthin"], "16.7 30.0 0.9": ["damnable"], "-4.3 8.3 4.9": ["dramatizations"], "8.3 8.2 10.5": ["wacked"], "-0.8 7.5 -0.1": ["worthier"], "6.2 12.7 15.3": ["repopulating"], "-5.2 0.2 6.8": ["bassoonist"], "-0.2 10.4 6.5": ["aurally"], "-6.4 4.6 29.5": ["rotis"], "0.6 6.0 2.2": ["spotkick"], "6.0 13.7 9.0": ["hatin"], "6.9 7.5 -0.3": ["blabbed"], "-4.3 6.3 11.5": ["midtempo"], "7.4 2.4 9.5": ["ukuleles"], "15.3 11.4 8.9": ["delightedly"], "-3.3 7.4 -0.9": ["heartwrenching"], "6.1 18.5 8.5": ["bugles"], "-2.6 4.3 -0.2": ["signposting"], "3.2 22.0 -2.1": ["assualt"], "12.5 26.1 5.1": ["rampart"], "16.0 5.4 10.4": ["poaches"], "4.4 13.6 9.9": ["stockholding"], "3.1 -2.8 2.6": ["polyols"], "22.9 -3.9 5.2": ["equalweight"], "6.9 5.7 10.5": ["foamed"], "15.0 11.4 14.3": ["candelabras"], "-4.3 1.1 3.3": ["quartiles"], "2.1 15.5 33.6": ["bucktails"], "7.0 4.7 9.9": ["clinton"], "3.2 5.9 4.0": ["nonpaying"], "-2.0 7.0 10.0": ["swingmen"], "3.6 9.0 3.9": ["depressurization"], "9.5 4.2 27.7": ["soapstone"], "8.9 -0.8 28.3": ["decoupage"], "6.4 1.3 9.2": ["postretirement"], "4.1 22.0 3.4": ["unquote"], "0.1 -1.9 12.7": ["exon"], "7.1 8.1 9.8": ["footman"], "4.7 17.6 19.9": ["buckthorn"], "1.3 12.1 10.0": ["kettlebells"], "-0.5 -2.5 -3.2": ["ghostwritten"], "-1.2 1.0 0.3": ["visting"], "-3.4 11.2 7.3": ["defunded"], "4.7 13.3 7.2": ["natter"], "4.3 -3.5 6.5": ["dustups"], "-1.3 8.6 5.9": ["panitumumab"], "22.1 14.9 15.2": ["slavering"], "4.1 3.3 11.4": ["stimulators"], "-3.7 12.4 19.0": ["heartworms"], "-2.3 11.6 -0.8": ["intuitiveness"], "6.2 9.6 2.2": ["calibrates"], "-0.6 4.0 16.6": ["seaworthiness"], "3.2 5.6 15.1": ["drayage"], "-1.7 1.0 19.8": ["fluorite"], "3.4 -5.0 6.4": ["eo"], "9.9 26.6 2.0": ["immanent"], "4.7 -1.5 13.9": ["weavings"], "5.0 9.2 30.7": ["mealy"], "9.8 4.8 22.3": ["wheatgrass"], "-3.9 3.0 5.9": ["dualling"], "-2.6 -0.4 2.6": ["pyrexia"], "7.4 2.6 2.1": ["relabeled"], "0.8 4.9 12.6": ["ruminates"], "5.7 10.9 13.8": ["psp"], "4.2 4.6 1.9": ["nonperformance"], "0.3 15.3 8.8": ["goalkickers"], "0.2 14.3 12.6": ["multiplay"], "8.8 20.0 6.2": ["secretively"], "9.4 -6.7 3.3": ["jazzing"], "8.2 5.4 12.6": ["crasher"], "6.3 22.1 48.6": ["gamefish"], "14.4 2.5 16.6": ["sauropod"], "16.0 -4.1 12.5": ["serv"], "-0.3 1.9 12.7": ["orthopedists"], "-1.7 5.8 24.3": ["sauteing"], "8.8 16.0 10.0": ["multiverse"], "-3.6 5.5 14.4": ["tambon", "dhun"], "3.6 0.8 8.5": ["carter"], "0.9 1.7 13.1": ["pressings"], "1.0 15.4 10.1": ["roust"], "5.2 5.6 2.7": ["computationally"], "-2.2 5.4 12.0": ["cathodes"], "9.5 9.3 5.1": ["swaggers", "analogizes"], "13.6 1.8 9.2": ["chockablock"], "16.6 -2.6 8.6": ["impresarios"], "7.7 1.6 23.7": ["elderberry"], "-2.2 10.0 -4.6": ["encumbering"], "1.6 9.7 15.8": ["towboats"], "12.0 6.4 16.5": ["bluebonnets"], "12.6 6.0 6.6": ["biochip"], "-0.9 9.3 -2.6": ["zealousness"], "1.2 9.5 0.1": ["unresponsiveness"], "0.0 11.9 6.5": ["derangement"], "8.0 11.6 6.9": ["commodified"], "9.6 3.9 11.3": ["chatshow"], "-1.4 4.4 6.1": ["bookmarklet"], "1.8 26.1 17.1": ["disobeys"], "2.9 10.7 8.6": ["bedclothes"], "3.6 4.6 -0.2": ["hightailed"], "-2.4 -1.9 2.3": ["raunchier"], "-3.1 8.5 12.6": ["sarcomas"], "-2.9 10.6 5.8": ["glovework"], "4.9 2.2 -7.2": ["manroland"], "9.6 12.9 -3.0": ["forswear"], "1.1 -1.8 -1.8": ["medtech"], "-3.8 13.6 16.1": ["leukocytes"], "2.2 14.6 14.5": ["maleness"], "6.0 5.2 10.2": ["picaresque"], "-1.5 12.7 12.0": ["hauteur"], "7.9 8.6 19.7": ["roundworms"], "-2.3 4.2 7.6": ["mridangam"], "-3.0 11.4 9.4": ["diurnal"], "7.9 7.2 8.6": ["bigscreen"], "-3.8 9.2 13.2": ["borewells"], "16.8 9.1 10.0": ["freefalling"], "-2.7 1.7 20.4": ["hepatocytes"], "1.8 11.0 0.3": ["psychographic"], "-2.4 0.4 10.2": ["midcareer"], "5.9 -5.4 7.3": ["progam"], "-5.5 0.9 18.7": ["longboarding"], "-7.5 5.1 0.5": ["wkt"], "1.5 2.7 12.7": ["dito"], "2.0 6.1 5.8": ["meddles"], "2.2 8.2 11.7": ["oldtimers"], "6.6 13.4 31.9": ["bobbers"], "10.3 14.1 7.2": ["unfruitful"], "7.9 11.6 0.3": ["penumbra"], "5.8 7.2 5.8": ["cosmodrome"], "-9.5 6.6 -6.6": ["audios"], "-1.2 5.1 3.8": ["fouth"], "-8.2 -1.5 3.7": ["reanalyzed"], "13.8 6.1 16.9": ["jumpin"], "1.6 7.6 1.0": ["dynamometer"], "6.0 3.0 14.1": ["balustrade"], "8.9 6.0 6.4": ["chipboard"], "5.9 1.2 5.6": ["fructify"], "-0.3 -0.2 11.6": ["ovulate"], "4.0 11.0 4.4": ["deactivates"], "11.0 6.8 10.7": ["gadflies"], "4.5 3.8 1.7": ["lecterns"], "-3.7 5.8 8.3": ["renin"], "25.4 15.4 12.9": ["pipsqueak"], "1.7 13.7 7.6": ["tifosi"], "12.3 24.2 -0.0": ["nonviolently"], "6.1 28.1 9.6": ["murderously"], "7.7 -2.2 10.7": ["brassieres"], "8.3 25.2 14.0": ["unlovable"], "6.6 6.7 -2.3": ["beepers"], "-3.8 4.3 49.7": ["lobstering"], "-14.4 3.8 2.3": ["hydroquinone"], "-4.2 4.2 15.5": ["earthier"], "-3.1 7.1 4.1": ["todo"], "7.3 28.6 4.8": ["vassals"], "11.4 4.9 20.1": ["caiman"], "-0.1 -1.9 -2.4": ["inlcuding"], "20.4 24.1 21.6": ["fucker"], "8.1 0.9 17.4": ["jacquard"], "8.9 18.0 5.3": ["paramours"], "5.8 8.6 17.0": ["frankfurters"], "8.0 8.2 7.7": ["alphabetized"], "1.8 6.4 8.8": ["glycoprotein"], "20.8 8.2 4.8": ["pulsates"], "-10.5 23.4 7.5": ["unfaithfulness"], "1.2 4.4 4.6": ["indiplon"], "13.6 10.7 6.3": ["colossally"], "-0.1 -2.8 8.0": ["rehires"], "4.9 4.1 19.6": ["glassmaking"], "11.6 10.0 16.9": ["hemorrhoid"], "-0.2 8.7 20.6": ["apiary"], "6.9 10.4 5.9": ["tellin"], "21.0 0.6 8.2": ["heftiest"], "-2.8 10.4 1.9": ["collegues"], "-3.0 8.4 21.0": ["mulatto"], "11.2 4.4 3.0": ["integrally"], "-4.6 18.7 2.9": ["maximalist"], "2.9 3.4 -5.6": ["radiographer"], "12.9 5.2 4.9": ["monopole"], "12.1 12.0 17.5": ["waterspout"], "4.7 10.3 8.6": ["overreaches"], "-11.5 1.0 10.9": ["streamflow"], "5.7 8.7 20.5": ["admiralty"], "3.9 -1.1 7.6": ["preem"], "3.0 20.9 16.6": ["backcheck"], "-4.3 0.6 11.1": ["autocatalysts"], "1.6 17.2 7.4": ["zag"], "5.8 10.1 4.3": ["energizer"], "7.1 18.2 13.4": ["warbles"], "11.8 1.5 4.3": ["groundbreaker"], "-1.7 13.0 11.5": ["almanacs"], "6.4 8.1 5.2": ["vistors"], "4.4 6.8 18.9": ["drawling"], "4.1 -1.0 -0.4": ["suh"], "-5.1 13.3 9.2": ["ransomed"], "2.8 12.3 10.5": ["plagiarist"], "6.2 -1.6 0.6": ["vu"], "9.1 5.4 17.3": ["wort"], "-0.1 -0.2 6.7": ["rebating"], "-3.3 7.9 -0.3": ["intracranial"], "15.1 3.9 2.3": ["toddling"], "2.4 7.6 12.3": ["noblewoman"], "-4.3 4.7 9.7": ["landslips"], "-0.3 12.7 -1.0": ["discriminative"], "18.7 8.5 13.7": ["dazzler"], "5.8 11.7 3.3": ["nanopore"], "14.9 11.1 2.2": ["playrooms"], "-5.6 4.5 9.8": ["simplex"], "-3.1 16.2 11.6": ["haughtiness"], "-2.5 5.8 -4.0": ["collateralised"], "-4.6 14.5 -1.5": ["inadmissibility"], "3.2 8.9 9.6": ["nontransferable"], "15.1 30.4 7.2": ["frenemy"], "7.0 22.3 9.3": ["forearmed"], "7.7 4.9 7.0": ["nebbish"], "-0.1 17.7 8.8": ["whiteouts"], "-0.6 -1.2 -2.6": ["conceptualisation"], "11.4 30.6 13.2": ["treacherously"], "-10.4 6.5 16.1": ["bodychecking"], "-1.3 20.3 4.4": ["epistemological"], "-8.1 2.0 4.3": ["diamorphine"], "-6.0 7.6 9.1": ["newsworthiness"], "10.3 5.9 11.0": ["orgiastic"], "8.0 5.9 2.3": ["consumptions"], "-13.6 8.8 4.8": ["dasatinib"], "1.8 17.7 14.7": ["backchecking"], "-0.6 7.6 -0.2": ["noncontact"], "2.9 6.4 7.6": ["bowsers"], "6.0 11.8 13.4": ["jaywalkers"], "2.2 20.8 -0.8": ["equivocating"], "1.5 1.5 4.6": ["scrutineers"], "6.4 4.5 43.3": ["dorado"], "18.4 15.8 10.1": ["haplessly"], "13.6 10.8 10.2": ["australian"], "8.3 7.7 7.8": ["goofiest"], "14.3 -5.7 -7.7": ["anounced"], "4.0 11.1 9.9": ["emulsifier"], "-3.4 9.7 8.0": ["overdiagnosis"], "4.3 11.0 4.6": ["typology"], "-3.6 3.5 11.6": ["ruminative"], "5.5 -1.2 10.8": ["groundskeeping"], "0.4 6.0 2.8": ["economise"], "3.5 3.1 7.8": ["flophouse"], "0.6 7.0 8.4": ["epitope"], "4.9 11.5 7.5": ["spendthrifts"], "14.8 15.0 2.5": ["sanctum"], "5.0 22.3 12.3": ["religionists"], "7.6 8.1 -1.2": ["walkman"], "5.8 5.5 8.1": ["pagination"], "8.7 4.8 9.3": ["luxuriating"], "2.2 7.6 -2.9": ["acknowleged"], "27.1 18.7 4.3": ["transnationals"], "8.7 8.4 6.6": ["proteome"], "-1.8 2.7 -0.5": ["backpacked"], "2.3 10.9 8.6": ["microlight"], "3.9 8.6 5.9": ["rearview"], "1.5 5.3 7.6": ["isotopic"], "0.1 5.1 11.6": ["sericulture"], "8.7 11.9 10.1": ["hm"], "-2.7 4.7 8.0": ["outhalf"], "1.3 7.5 23.8": ["composters"], "-5.4 2.5 4.5": ["cachexia"], "-5.7 0.8 13.2": ["downtempo"], "5.2 6.7 9.9": ["elastomeric"], "-4.0 6.0 12.8": ["charas"], "7.8 9.7 11.4": ["anomie"], "11.2 9.6 7.4": ["blindfolding"], "8.1 -5.2 7.2": ["choosier"], "-0.8 16.8 3.9": ["scrappiness"], "11.8 7.6 60.8": ["codfish"], "11.1 11.9 14.9": ["unix"], "-6.6 8.4 9.5": ["breastroke"], "-0.4 8.7 2.4": ["promptings"], "5.3 -6.6 2.5": ["guh"], "17.4 9.1 16.3": ["proboscis"], "3.8 11.1 7.5": ["scalar"], "2.2 9.9 5.6": ["declutter"], "9.7 2.1 4.9": ["moneysaving"], "8.8 7.6 20.9": ["speckles"], "7.8 12.4 21.3": ["chooks"], "6.9 4.8 2.0": ["acrimoniously"], "8.9 11.9 8.3": ["uploaders"], "18.3 16.3 15.6": ["earthmovers"], "-6.9 20.5 5.6": ["occurance"], "3.5 11.7 -0.6": ["requisitioning"], "6.9 7.5 -0.6": ["airconditioned"], "11.8 15.8 7.0": ["decrepitude"], "0.3 17.3 8.0": ["thoughtlessness"], "-0.1 6.2 8.4": ["nanofabrication"], "8.3 3.4 2.0": ["tepidly"], "14.3 14.1 22.7": ["scapes"], "10.2 2.7 5.0": ["smalltown"], "-7.4 16.7 14.5": ["deadheading"], "7.2 9.7 9.0": ["newspapering"], "1.1 9.4 2.5": ["mumbai"], "7.9 7.9 -3.6": ["progressiveness"], "-5.5 6.6 10.2": ["stratify"], "11.4 1.2 6.4": ["fascias"], "3.1 9.8 17.7": ["boatpeople"], "-4.8 8.6 2.0": ["articulations"], "7.3 15.4 12.8": ["preserver"], "6.7 10.5 6.9": ["unmeasured"], "16.0 39.7 9.2": ["evildoer"], "6.3 6.4 16.4": ["dhaba"], "10.2 8.1 10.6": ["splutter"], "16.8 15.7 12.9": ["bonk"], "17.0 -2.8 6.7": ["downscaled"], "6.1 4.2 2.8": ["majorettes", "magnetos"], "-0.4 6.8 7.1": ["photoresist"], "-6.9 7.5 -2.1": ["advocacies"], "10.2 7.0 12.8": ["pries"], "-3.6 21.4 3.4": ["emplaced"], "-5.0 17.5 2.6": ["intentionality"], "3.8 4.6 12.7": ["floppies", "gwang"], "-3.0 12.2 14.9": ["biocide"], "-2.0 9.3 14.1": ["fastbreaks"], "0.9 6.6 8.8": ["nuttier"], "9.7 3.5 -0.6": ["fiberoptic"], "18.4 34.3 7.6": ["flamethrowers"], "10.3 4.8 8.1": ["gargling", "tootling"], "22.6 5.8 5.4": ["pulsate"], "-2.7 5.3 8.2": ["rubrics"], "13.9 11.9 16.2": ["feller"], "2.2 0.7 3.7": ["defrayed"], "-11.5 2.7 -2.6": ["audiotaped"], "2.5 24.4 -0.8": ["smokescreens"], "-3.4 9.8 8.9": ["preplanning"], "-8.7 3.3 -1.5": ["serology"], "5.6 6.2 7.6": ["experimentalists"], "7.1 3.1 2.0": ["lanthanum"], "10.1 2.2 9.9": ["collaged"], "22.9 4.5 -0.3": ["whirred"], "-2.8 -2.8 7.8": ["dl"], "-5.4 3.4 8.2": ["unissued"], "0.6 5.3 9.2": ["neurofibromatosis"], "19.4 5.0 6.5": ["fugly"], "3.5 3.4 -6.1": ["gangraped"], "-2.0 11.7 15.1": ["subfloor"], "-5.0 7.8 3.8": ["fistulas"], "8.8 10.6 9.4": ["pharaonic"], "4.5 4.1 9.2": ["dum"], "-13.6 -2.7 3.8": ["hydromorphone"], "21.8 11.2 14.9": ["grabby"], "9.2 7.5 2.3": ["pervy"], "16.6 5.8 5.0": ["pirouetting"], "14.0 3.3 12.9": ["unrolling"], "9.4 17.6 19.1": ["bioluminescence"], "-5.0 6.7 4.8": ["reteam"], "-2.0 7.1 -7.8": ["affadavit"], "-10.5 7.6 -7.7": ["dictations"], "10.1 15.7 8.5": ["mutable"], "2.9 10.0 1.9": ["irreproachable"], "-0.0 6.5 12.8": ["everywoman"], "4.9 6.7 -2.6": ["tannoy"], "-2.1 -1.7 -1.5": ["motorcoaches"], "5.2 11.3 29.4": ["jerkbaits"], "-0.8 10.5 7.4": ["hypothecate"], "-8.7 17.2 7.2": ["regimentation"], "0.0 4.5 4.4": ["handpicking"], "8.0 20.6 9.8": ["ladylove"], "2.5 9.0 18.3": ["townie"], "-2.8 7.4 12.0": ["adagio"], "17.9 7.5 7.8": ["spookily"], "-8.5 12.7 3.6": ["immunosuppressant"], "-5.7 20.6 21.1": ["offspeed"], "1.8 9.2 -0.7": ["stonings"], "4.3 6.6 0.1": ["airhostess"], "7.7 -2.5 -0.6": ["srl"], "7.9 4.0 3.0": ["memristor"], "5.4 10.4 11.9": ["neurotoxins"], "-2.1 -4.4 8.3": ["jitney"], "7.9 16.2 17.1": ["racketeer"], "-0.2 12.2 12.1": ["delamination"], "4.9 2.4 4.9": ["smidgeon"], "-10.6 7.8 2.2": ["signability"], "-6.7 26.1 1.6": ["flightline"], "9.0 -0.3 20.4": ["felted"], "2.6 8.1 5.7": ["statically"], "-2.0 6.5 4.3": ["ofatumumab"], "1.5 3.9 11.9": ["bobsleds"], "-6.3 9.9 8.5": ["stepparents"], "6.0 16.9 9.2": ["backman"], "-2.2 8.9 -4.0": ["professionalized"], "10.9 7.3 7.9": ["lope"], "6.7 4.2 10.1": ["unpicked"], "-5.7 1.5 9.9": ["fluorosis"], "13.7 7.2 11.3": ["rocketship"], "-7.0 0.6 9.4": ["prorate"], "11.6 2.9 10.4": ["theming"], "10.3 7.4 1.7": ["commision"], "16.7 15.0 6.2": ["pockmarks"], "12.5 -0.8 7.8": ["swankiest"], "-1.7 17.3 2.4": ["uncorrupted"], "-0.9 12.9 13.6": ["attractants"], "5.9 -4.6 0.8": ["semiprofessional"], "-0.3 10.1 21.6": ["winegrowers"], "0.7 -0.1 7.2": ["serie"], "-3.8 3.4 4.6": ["rawer"], "4.3 10.0 54.0": ["whitebait"], "-0.7 -1.1 9.6": ["hardbound"], "3.3 17.9 -0.8": ["strategical"], "5.7 7.0 3.4": ["antibusiness"], "-4.2 4.5 4.5": ["superintendency"], "4.0 9.9 14.2": ["hemagglutinin"], "6.3 3.3 3.3": ["sniffy"], "-0.4 15.9 6.8": ["disingenuousness"], "11.0 15.8 12.3": ["swamplands"], "3.1 -0.3 11.3": ["spain"], "-2.6 3.0 -2.5": ["rofecoxib"], "-2.1 10.7 8.0": ["outstayed"], "-1.0 4.4 1.7": ["ditsy"], "20.7 8.4 23.2": ["harlequin"], "-6.1 19.0 10.5": ["apoptotic"], "0.2 4.7 1.9": ["delinked"], "2.5 11.0 3.3": ["malafide"], "4.8 3.8 7.3": ["losartan"], "8.9 18.6 16.4": ["tailgater"], "-3.9 -4.5 3.2": ["sexologist"], "5.0 4.0 1.9": ["typographic"], "-4.0 12.4 19.0": ["grillers"], "-4.7 -0.4 5.8": ["chauffer"], "-11.8 0.2 2.5": ["transferees"], "9.7 -1.8 16.9": ["pla"], "-6.7 3.7 14.1": ["scrapbookers"], "14.8 20.2 9.0": ["complacently"], "1.5 10.8 6.2": ["bleaches"], "-1.3 7.8 17.0": ["nonqualified"], "7.4 -0.9 2.9": ["estafa"], "7.0 10.4 10.4": ["recursive"], "8.2 5.4 4.3": ["secy"], "0.4 10.5 8.8": ["environnment"], "2.4 -7.4 0.4": ["reheard"], "6.4 4.7 11.0": ["fibrils"], "8.1 8.3 14.3": ["butte"], "3.2 -1.4 5.8": ["datasheet"], "6.8 11.7 13.6": ["unweighted"], "6.9 7.0 30.1": ["kohlrabi"], "20.3 9.9 29.2": ["marmot"], "6.2 15.8 3.9": ["shushing"], "3.9 12.0 5.1": ["scramjet"], "10.6 -0.3 10.5": ["kah"], "-9.7 5.7 8.0": ["fluconazole"], "20.5 7.1 25.4": ["knobby"], "9.9 5.1 7.0": ["explainer"], "28.5 27.8 11.8": ["anthill"], "1.7 13.3 10.8": ["classism"], "10.4 2.9 10.7": ["superglue"], "-4.5 8.7 8.1": ["legato"], "8.7 -0.0 12.6": ["palaeontologists"], "24.5 13.3 12.8": ["centaur"], "7.4 18.6 -1.9": ["surveilling"], "-7.2 14.4 8.3": ["dunums"], "10.8 14.3 24.0": ["shawarma"], "3.2 2.4 0.4": ["spectrophotometer"], "-1.5 4.6 5.9": ["reshot"], "12.8 11.7 20.5": ["birches"], "2.5 1.3 5.2": ["ance"], "17.0 14.6 -5.8": ["personifying"], "4.2 29.8 11.0": ["radioman"], "4.2 -2.9 9.5": ["prelaunch"], "7.4 6.7 27.1": ["outriggers"], "1.2 10.4 10.2": ["roundball"], "9.0 9.0 17.1": ["gargle"], "0.5 3.4 11.3": ["unworn"], "0.1 7.7 6.2": ["femto"], "11.8 0.2 10.5": ["loggia"], "14.2 7.5 -0.8": ["sytem"], "3.7 4.1 7.1": ["enthralls"], "-4.7 -0.3 8.1": ["externship"], "-3.5 4.2 10.2": ["pluripotency"], "-7.4 8.8 1.7": ["stutterers"], "6.6 17.7 6.2": ["seductions"], "4.3 10.2 5.1": ["relatedness"], "3.0 37.7 -6.6": ["mujahadeen"], "2.7 6.8 12.1": ["homerooms"], "1.8 -0.6 -4.0": ["catalyzes"], "-3.3 3.6 -1.2": ["vols"], "-2.2 5.5 1.6": ["subventions"], "11.6 0.4 7.6": ["matchbook"], "6.1 3.2 10.4": ["sirtuins"], "-1.5 -1.3 5.4": ["msg"], "-6.5 -0.7 1.5": ["apprenticing"], "-1.3 6.1 16.1": ["gardenias"], "9.4 -0.5 -0.1": ["developement"], "-1.0 -0.6 27.9": ["clementines"], "0.3 4.6 3.1": ["daydreamed"], "3.2 12.2 4.8": ["espousal"], "-11.2 0.4 0.4": ["salbutamol"], "8.8 -4.7 18.5": ["mei"], "-0.4 14.3 5.9": ["accedes"], "-0.6 4.0 2.2": ["incentivizes"], "12.0 19.6 5.9": ["beguile"], "6.8 2.6 1.9": ["reroutes"], "6.5 4.4 5.1": ["dally"], "12.7 5.3 12.0": ["columnar"], "6.0 15.7 0.6": ["ignoramuses"], "-1.5 22.7 10.7": ["naxalism"], "-5.3 -1.5 8.8": ["aestheticians"], "4.5 5.8 7.3": ["macroeconomy"], "-3.3 5.2 22.9": ["padi"], "2.6 7.3 -3.5": ["xxxx"], "12.3 3.3 3.3": ["bizzare"], "8.4 8.2 20.2": ["bootie"], "2.6 15.8 7.3": ["degreaser"], "-2.6 4.1 4.1": ["unexercised"], "8.2 14.1 13.6": ["tightwad"], "10.0 0.4 10.3": ["ireland"], "1.2 4.2 5.3": ["aspirated"], "6.6 -1.1 11.8": ["imec"], "12.4 3.7 11.3": ["clappers"], "12.7 7.4 10.8": ["unsustainability"], "14.3 12.1 15.3": ["douchebags"], "-7.5 9.4 4.1": ["easiness"], "2.1 2.0 0.2": ["pleader"], "-7.2 4.5 2.8": ["contraindication"], "8.7 12.7 8.2": ["fidgets"], "9.9 4.3 3.5": ["colons"], "-5.6 20.7 13.4": ["bunter"], "-0.5 12.0 3.9": ["outplays"], "-0.5 7.7 9.0": ["econometric"], "8.8 8.0 6.3": ["annotating"], "1.5 4.7 5.2": ["dias"], "9.3 5.1 4.8": ["skywalks"], "-5.0 15.2 10.4": ["hartals"], "-4.6 19.7 -0.4": ["brutalization"], "5.2 28.6 4.8": ["propagandizing"], "-8.6 3.3 10.1": ["requalify"], "13.9 0.9 14.9": ["cofferdam"], "2.2 4.5 14.1": ["doghouses"], "14.8 14.8 14.9": ["poops"], "4.6 14.1 10.4": ["relearned"], "3.7 8.5 12.0": ["proteasome"], "6.9 3.0 -1.6": ["bannered"], "-4.2 4.8 14.2": ["bistate"], "5.6 1.1 9.1": ["axel"], "5.2 2.3 9.5": ["scuzzy"], "10.2 6.9 9.4": ["weedkiller"], "20.3 1.9 19.0": ["choc"], "6.0 22.0 10.7": ["dissemble"], "28.9 17.4 2.5": ["armageddon"], "1.7 8.0 15.3": ["hyphy"], "16.8 11.4 5.1": ["attachable"], "0.1 3.0 16.0": ["stateful"], "4.8 6.9 9.7": ["dreariness"], "3.1 -5.0 10.5": ["sana"], "3.0 7.8 13.2": ["oxidised"], "-10.3 9.9 9.3": ["immunocompromised"], "2.4 21.8 1.3": ["disgraces"], "12.4 11.3 6.3": ["awsome"], "-4.5 12.5 7.6": ["inswinging"], "1.1 15.9 -0.1": ["jailbreaks"], "20.1 15.0 8.3": ["muscleman"], "7.6 23.9 8.1": ["obscurantist"], "1.8 10.1 -1.6": ["grassfire"], "10.2 12.7 0.6": ["megatons"], "-2.3 7.2 3.4": ["dispersions"], "2.4 12.5 8.9": ["positrons"], "4.7 27.4 8.2": ["nonbeliever"], "2.6 10.7 8.8": ["waveguides"], "-3.4 5.8 2.9": ["amicus"], "-11.2 11.6 5.7": ["councilperson"], "0.6 11.2 27.4": ["nestlings"], "3.9 6.7 14.7": ["patters"], "9.1 7.5 10.5": ["fractals", "schwannoma"], "4.3 9.3 -4.9": ["uncomplimentary"], "17.2 14.6 23.3": ["jackrabbit"], "10.3 7.0 12.7": ["drillings"], "3.6 7.4 6.2": ["jordan"], "4.9 -0.7 2.8": ["mov"], "3.3 2.9 15.5": ["plummy"], "1.0 10.9 37.1": ["muskellunge"], "0.6 6.4 13.4": ["polysaccharides"], "-2.4 18.8 2.8": ["patroling"], "5.2 13.2 2.5": ["outclasses"], "11.0 9.5 14.3": ["nonpareil"], "7.2 11.4 10.6": ["nintendo"], "2.4 2.2 6.4": ["emtricitabine"], "4.3 8.7 -2.0": ["comparision"], "10.3 4.6 10.4": ["kerchief"], "3.8 -1.1 5.3": ["alledged"], "-2.1 17.8 5.8": ["reactively"], "1.2 6.3 12.1": ["medina"], "-3.9 2.6 14.3": ["micronutrient"], "6.3 12.6 13.4": ["electroshock"], "9.1 19.1 13.4": ["maegashira"], "-5.5 -3.0 12.6": ["fluorspar"], "11.7 -9.6 14.4": ["chee"], "-2.4 4.5 8.1": ["perfecto"], "8.9 9.0 -2.8": ["gladden"], "7.0 -1.3 11.2": ["mochas"], "9.4 -4.5 14.5": ["koh"], "3.7 18.6 10.2": ["stoppable"], "11.2 1.9 10.5": ["credenza"], "-0.4 9.3 9.3": ["tattle"], "2.4 10.0 7.8": ["stampings"], "5.1 4.0 7.0": ["concreted"], "14.5 4.9 9.7": ["superannuated"], "4.5 -1.4 9.9": ["inf"], "3.5 19.9 5.1": ["unsaved"], "6.6 2.7 0.5": ["downscaling"], "15.0 18.0 12.8": ["munchkin"], "5.1 4.6 0.5": ["saftey"], "7.5 6.2 16.7": ["skying"], "6.6 14.9 2.6": ["somebodies"], "-0.3 9.7 11.4": ["adenoviruses"], "9.0 6.3 15.2": ["congregates"], "5.9 3.5 13.9": ["kim"], "1.2 16.5 12.2": ["belay"], "-3.5 4.3 -2.8": ["outscores"], "13.7 5.3 6.8": ["shr"], "11.3 2.7 5.5": ["thons"], "11.8 -1.1 13.7": ["appliques"], "2.5 17.1 5.2": ["insufferably"], "-1.1 1.3 7.2": ["rehoming"], "8.3 4.9 8.7": ["circ"], "12.7 -0.9 3.2": ["sedately"], "12.3 2.0 8.4": ["tuneless"], "0.9 9.9 32.1": ["huckleberries"], "6.7 7.3 3.2": ["fortieth"], "10.3 29.1 6.1": ["antimissile"], "10.9 2.7 20.5": ["cockatiel"], "-5.2 12.1 13.3": ["bachelorhood"], "-1.2 12.6 14.7": ["ultralights"], "8.8 3.6 8.8": ["upwardly"], "12.9 9.5 32.1": ["nacho"], "8.3 8.6 8.1": ["bloviating"], "1.3 11.7 1.8": ["malleability"], "-6.2 9.5 5.7": ["minocycline"], "11.6 5.1 13.1": ["pictographs"], "-0.6 9.5 12.9": ["backstroker"], "8.8 7.0 13.6": ["unadventurous"], "-2.2 4.4 5.4": ["ooma", "isozyme"], "15.6 6.3 17.4": ["sweeties"], "15.7 9.2 16.7": ["cartoonishly"], "7.3 6.7 1.7": ["rowdiest"], "-2.8 3.3 6.9": ["innerwear"], "3.1 3.2 8.6": ["psychedelics"], "-3.6 -1.0 1.3": ["absorbable"], "4.6 22.6 7.1": ["killin"], "10.9 -3.8 0.5": ["agm"], "12.3 19.2 16.4": ["motherfuckers"], "3.4 14.3 -2.3": ["oversensitive"], "2.9 24.2 6.9": ["unforgiveable"], "8.0 6.9 9.1": ["dreidels"], "8.0 7.5 5.6": ["tweeners"], "-6.0 6.8 5.1": ["pemetrexed"], "4.9 5.2 5.2": ["obviated"], "-3.7 5.0 1.8": ["downvalley"], "15.1 13.3 9.9": ["juicers"], "7.8 8.2 25.7": ["samosa"], "1.3 20.8 8.5": ["meekness"], "17.4 9.3 8.7": ["sidling"], "-2.2 9.8 1.8": ["misinterprets"], "18.4 10.1 6.5": ["quivered"], "6.1 5.8 4.2": ["consigns"], "2.0 5.0 4.6": ["overbuild"], "3.3 7.1 46.7": ["minke"], "10.6 17.3 19.1": ["shrews"], "-2.4 6.7 -8.4": ["impliedly"], "4.8 5.8 9.2": ["muddier"], "-5.0 3.8 8.2": ["ranched"], "-1.3 8.5 12.4": ["thermocouple"], "7.4 11.3 9.8": ["cupolas"], "-0.2 9.2 4.0": ["revivalists"], "13.6 13.7 11.7": ["dadgum"], "-5.3 0.5 4.2": ["trihalomethanes"], "12.7 13.4 8.0": ["glints"], "16.3 11.2 12.3": ["hypercompetitive"], "1.8 -1.5 16.2": ["cotillion"], "10.1 2.1 3.4": ["tooted"], "0.4 5.9 10.6": ["bracingly"], "12.8 8.2 20.3": ["windowpane"], "8.3 -1.3 1.6": ["precent"], "6.6 7.8 10.8": ["dropdown"], "-6.7 10.5 8.4": ["artesunate"], "3.9 4.2 2.8": ["lingual"], "7.9 17.7 20.9": ["oleander"], "7.5 -0.3 12.8": ["easter"], "8.2 5.9 12.0": ["smooches"], "2.9 9.0 5.8": ["contactor"], "-9.4 1.7 -7.1": ["pulmonology"], "4.4 7.5 16.0": ["valance"], "-9.0 3.1 10.2": ["nonrenewal"], "2.9 7.6 4.3": ["suffragette"], "8.5 8.5 12.0": ["prophylactics"], "4.2 -1.2 10.1": ["getups"], "1.8 11.1 0.6": ["frontrunning"], "-3.4 1.4 4.8": ["gerontologist"], "-2.9 7.2 10.0": ["handspring"], "-5.5 7.2 9.2": ["shearling"], "5.3 0.7 2.8": ["repackages"], "6.2 9.8 25.1": ["yarrow"], "-1.4 1.2 0.3": ["cis"], "15.3 7.6 8.8": ["weekslong"], "14.2 26.1 13.9": ["chokepoint"], "-4.2 9.2 11.6": ["serotype"], "-10.7 7.3 -1.5": ["bailable"], "-7.3 8.2 4.9": ["overtreatment"], "-0.5 7.4 10.3": ["nonresponsive"], "1.0 8.7 2.5": ["reinvigorates"], "5.2 3.8 10.9": ["vibratory"], "4.6 9.8 -0.3": ["trivialization"], "7.5 5.9 2.0": ["metamorphoses"], "-3.1 18.0 8.9": ["empiricism"], "-0.0 3.5 3.2": ["leftback"], "-2.9 5.3 1.9": ["linaclotide"], "-4.3 6.0 14.0": ["mellows"], "6.3 15.4 12.5": ["mafioso"], "3.8 3.8 4.0": ["isolators"], "-2.3 12.7 4.0": ["chattels"], "6.4 -0.1 13.9": ["api"], "9.4 14.7 15.9": ["rimming"], "16.2 8.6 14.2": ["droppers"], "5.7 7.3 0.1": ["ejaculated"], "6.7 8.3 7.9": ["forsook"], "5.5 2.9 7.7": ["fastens"], "1.0 13.9 7.8": ["eros"], "1.8 11.8 13.8": ["bitchiness"], "17.4 11.7 10.4": ["unchained"], "6.3 0.8 18.2": ["anglo"], "-10.1 13.0 0.9": ["assaultive"], "7.8 24.5 6.9": ["perishes"], "-2.7 1.3 -0.1": ["avanafil"], "5.8 1.7 5.2": ["soapie"], "9.2 12.4 20.4": ["kestrels"], "18.2 27.5 15.1": ["reaper"], "1.9 5.8 24.7": ["agar"], "6.0 5.9 6.4": ["bleats"], "8.5 5.1 10.5": ["mailrooms"], "7.0 31.5 0.5": ["jehadis"], "6.2 7.2 4.9": ["childproof"], "-6.5 12.0 4.7": ["releasable"], "1.1 10.3 6.7": ["putdowns"], "-4.6 17.9 3.8": ["pigeonholing"], "14.4 13.9 14.5": ["reanimate"], "2.0 3.7 14.8": ["kaftan"], "9.7 8.7 9.1": ["tweakers"], "3.6 9.5 2.7": ["aircon"], "7.3 16.3 11.8": ["dropkicks", "hime"], "-2.6 17.0 8.5": ["addon"], "-2.8 2.7 2.3": ["mothered"], "6.7 24.3 10.3": ["gunfighter"], "2.7 18.5 -3.2": ["demonstratively"], "2.7 3.3 13.5": ["skateparks"], "7.0 4.0 5.4": ["footboard"], "15.3 10.7 30.3": ["porkers"], "17.1 4.9 7.3": ["lg"], "-1.5 -0.6 9.1": ["mes"], "3.2 0.3 2.8": ["ld"], "-0.0 0.6 1.4": ["pontificated"], "4.9 9.2 10.6": ["cavitation"], "11.1 11.8 -0.5": ["tunnelled", "attact"], "6.5 12.2 10.1": ["synchronously"], "23.2 7.8 8.1": ["levitated"], "1.0 8.0 5.6": ["begrudged"], "-13.9 4.6 -0.1": ["neurocognitive"], "-5.6 7.9 11.2": ["sigmoidoscopy"], "4.9 1.7 1.5": ["tek"], "6.6 8.2 6.9": ["floozy"], "5.6 6.6 17.6": ["tam"], "-8.0 3.7 9.5": ["histologic"], "-3.2 -0.5 18.1": ["anna"], "5.5 10.1 30.1": ["kingfishers"], "3.7 7.1 -1.0": ["aerostructures"], "5.0 12.5 0.6": ["commiseration"], "12.9 0.1 13.9": ["saucepans"], "-3.3 0.4 -1.2": ["webstore"], "12.9 15.1 0.7": ["gibe"], "1.3 7.4 3.3": ["tasering"], "0.4 5.8 7.0": ["periodicity"], "5.5 -0.5 9.1": ["gp"], "-0.8 12.9 0.5": ["permeation"], "10.0 10.6 1.3": ["blackspots"], "0.1 10.9 21.3": ["tao"], "-6.2 2.9 5.5": ["pedagogic"], "10.2 13.5 16.6": ["croaks"], "4.3 -2.4 26.1": ["delish"], "7.5 4.7 18.4": ["tarballs"], "3.1 5.7 17.0": ["rehydrated"], "7.7 9.6 16.7": ["gunmetal"], "-8.7 12.7 3.4": ["editorialize"], "-5.3 2.6 26.2": ["icewine"], "9.0 23.7 10.3": ["nunchuck"], "9.1 7.9 9.2": ["guffawed"], "4.2 10.5 7.9": ["decelerates"], "-5.9 6.6 11.4": ["digestibility"], "0.5 17.8 8.2": ["consorts"], "-8.5 15.5 2.8": ["organophosphates"], "-2.3 13.9 9.0": ["epistemology"], "-0.2 7.0 8.3": ["stutterer"], "9.3 9.4 23.4": ["ketch"], "-1.2 7.4 6.4": ["unroadworthy"], "-7.9 7.0 5.3": ["cerebrovascular"], "4.7 6.1 6.3": ["electricty"], "-5.1 8.5 11.5": ["bronchoscopy"], "-2.2 20.1 5.3": ["theism"], "2.4 7.6 14.7": ["bevel"], "9.3 9.0 36.3": ["dugongs"], "1.6 4.1 4.5": ["weighbridge"], "1.9 4.7 3.9": ["ambrisentan"], "8.7 14.3 8.7": ["bumpkin"], "8.2 4.6 4.2": ["quells"], "7.3 13.3 8.3": ["survivalists"], "1.3 3.5 9.2": ["liquored", "scolaire"], "1.7 10.0 10.2": ["gradualism"], "-2.4 6.7 7.2": ["meditators"], "10.0 -0.3 17.8": ["damask"], "25.1 2.0 22.3": ["jiggly"], "6.1 9.9 29.4": ["overexploitation"], "3.7 6.1 9.3": ["cassock"], "8.6 11.6 15.2": ["pustules", "supuesto"], "2.8 11.5 8.3": ["greenbelts"], "4.7 2.5 26.3": ["mooncakes"], "-0.4 3.3 5.1": ["percussions"], "7.9 8.1 29.8": ["ramekin"], "-0.9 2.3 14.4": ["crofting"], "-8.0 14.0 1.5": ["cashiered"], "1.0 5.5 5.2": ["dragstrip"], "9.0 8.7 2.7": ["globetrotter"], "9.1 11.7 2.4": ["illogically"], "10.6 21.5 7.1": ["gloats"], "19.4 5.8 7.7": ["hoovering"], "-3.6 12.3 0.8": ["testator"], "2.0 22.6 4.2": ["repents"], "-5.9 7.6 9.8": ["seismicity"], "9.5 9.8 7.3": ["doorbusters"], "-7.6 15.8 6.5": ["mitzvot"], "7.6 3.1 5.2": ["smooched"], "19.9 9.9 10.1": ["cartwheeling"], "-0.3 5.6 11.8": ["parenthetical"], "-0.3 16.6 9.6": ["delimited"], "2.7 4.4 6.9": ["backaches"], "15.6 -1.9 14.9": ["sheaves"], "4.6 11.3 2.7": ["anoints"], "6.7 7.3 7.4": ["ail"], "4.7 17.3 7.4": ["trekker"], "4.9 9.9 -2.6": ["decertifying"], "5.0 16.9 36.7": ["lampreys"], "0.9 9.7 6.5": ["prefixed"], "14.4 -0.2 15.4": ["corking"], "-2.5 17.4 1.3": ["howsoever"], "4.3 11.5 15.3": ["mosh"], "11.5 18.7 18.4": ["meanie"], "18.9 2.7 9.8": ["shrs"], "4.6 7.3 3.3": ["hydroxyl"], "5.8 6.7 19.7": ["chads"], "-1.7 7.5 6.1": ["underplays"], "15.5 0.8 2.9": ["teamsters"], "11.9 1.1 4.0": ["factbox"], "8.2 13.0 5.0": ["evolutionist"], "6.0 9.6 10.3": ["bootloader"], "-2.3 6.6 7.9": ["golimumab"], "0.5 20.0 10.5": ["negroes"], "11.8 17.2 5.8": ["smote"], "1.7 7.2 6.8": ["fader"], "-7.9 4.9 0.2": ["unblinded"], "5.0 6.8 19.5": ["ornithological"], "8.0 5.3 13.7": ["bronzing"], "11.9 12.5 10.2": ["supping"], "-8.8 8.9 4.8": ["voreloxin"], "-8.8 2.9 11.4": ["dayparts"], "0.9 9.3 13.0": ["hypochondria"], "-5.8 12.9 1.6": ["disempowerment"], "5.9 14.4 13.0": ["arabesque"], "4.3 -1.8 2.8": ["reprographics"], "0.8 3.4 0.1": ["frivolities"], "4.6 15.6 10.7": ["scarcities"], "6.7 12.9 2.6": ["anarchistic"], "4.8 3.3 10.7": ["treehouses"], "-5.8 14.4 5.3": ["asanas"], "-2.1 2.3 30.7": ["marjoram"], "6.7 3.9 21.3": ["precut"], "0.4 3.6 7.8": ["vous"], "6.9 1.1 8.7": ["sydney"], "-2.7 11.0 24.0": ["pilaf"], "-4.5 3.0 17.1": ["palatability"], "3.7 7.4 17.1": ["pleat"], "9.6 3.3 4.3": ["overvaluing"], "-3.7 1.1 12.5": ["ine"], "8.1 1.6 10.0": ["grands"], "6.0 3.2 6.6": ["econometrics"], "18.1 9.0 -0.9": ["bamboozling"], "9.6 16.5 23.0": ["shuttlecock"], "3.1 12.6 1.7": ["unlatched"], "5.0 5.9 35.7": ["gooseberries"], "5.5 11.3 13.8": ["schist"], "-1.9 3.2 3.1": ["bcfe"], "-2.4 9.5 12.6": ["meiosis"], "0.1 19.8 3.8": ["propagandize"], "20.2 18.4 13.6": ["waggling"], "1.9 16.5 5.3": ["discontinuities"], "11.8 -0.7 5.4": ["toyboy"], "-6.7 4.5 8.4": ["homozygous"], "7.6 -2.4 9.1": ["aahing"], "7.2 6.6 15.5": ["nookie"], "9.1 6.6 3.7": ["tightknit"], "5.2 9.5 9.8": ["greenhorns"], "-2.0 25.8 9.9": ["counteraction"], "2.5 18.8 10.7": ["algebraic"], "-5.7 19.8 -1.3": ["proselytism"], "6.7 -0.3 7.3": ["teetotalers"], "1.1 2.1 11.8": ["verandahs"], "-0.8 6.1 20.7": ["limoncello"], "-9.1 4.5 6.4": ["dramaturg"], "13.9 2.6 4.2": ["fizzes"], "3.1 15.2 4.1": ["schizoid"], "3.1 13.4 -2.1": ["seperately"], "26.0 6.5 15.7": ["phosphorescent"], "-4.5 7.4 18.4": ["bhang"], "-1.0 10.5 0.3": ["resolvable"], "-4.7 10.6 14.2": ["countable"], "18.7 8.2 0.8": ["cozies"], "0.6 5.3 10.5": ["cosmeceuticals"], "-4.5 -6.1 10.1": ["concours"], "2.7 12.9 11.3": ["liposome"], "7.9 14.7 12.1": ["integers"], "-3.6 9.8 4.3": ["uncircumcised"], "4.6 4.3 10.1": ["altarpiece"], "6.6 5.4 19.7": ["gangmasters"], "-4.1 5.7 2.8": ["communions"], "2.7 7.1 -5.7": ["phonecalls"], "14.5 10.7 12.3": ["volleyballs"], "18.3 19.0 15.6": ["cheesiest"], "6.4 4.3 2.3": ["pinups"], "-5.6 5.6 3.8": ["historicity"], "0.6 15.5 2.2": ["monetarist"], "9.8 11.5 8.6": ["gropes"], "6.3 1.7 2.1": ["bifurcate"], "1.8 17.8 11.4": ["incrementalism"], "-2.8 10.6 7.1": ["rpms"], "-0.9 15.3 7.8": ["evaporative"], "-1.0 0.5 0.9": ["rpt"], "3.3 4.2 18.7": ["wakeboarders"], "0.2 1.9 10.2": ["genealogies"], "-6.9 5.5 5.0": ["subclinical"], "-5.7 11.2 1.6": ["speach"], "-5.8 14.6 8.5": ["uplinks"], "10.3 0.7 10.2": ["yih"], "20.6 11.3 11.6": ["crapping"], "4.1 -4.0 8.9": ["vegas"], "14.7 15.4 14.3": ["scooper"], "15.1 8.7 5.7": ["shyster"], "4.5 2.0 5.4": ["nes"], "15.3 6.2 16.0": ["misted"], "10.1 19.2 9.3": ["unmovable"], "-2.7 16.5 2.5": ["ignitions"], "12.6 7.5 -4.2": ["electrifies"], "11.0 -1.3 10.3": ["toddle"], "2.9 -1.1 19.5": ["bouzouki"], "7.4 4.2 13.1": ["bf"], "-6.7 -2.7 4.7": ["harpsichordist"], "8.6 -0.1 3.0": ["tw"], "-15.9 3.5 9.7": ["enplanement"], "2.7 9.7 5.2": ["cheekiness"], "4.6 1.3 13.2": ["doon"], "4.1 20.8 4.4": ["dauntless"], "2.1 10.9 2.9": ["forbear"], "-10.9 1.8 -4.0": ["thrombolysis"], "-0.6 6.3 17.9": ["drybulk"], "5.3 -4.9 8.0": ["delle"], "3.3 1.9 13.2": ["ermine"], "12.3 11.1 6.4": ["bestest"], "6.9 7.2 6.2": ["opaqueness"], "4.1 12.7 8.1": ["crudity"], "0.2 19.6 12.4": ["vexation"], "-3.8 8.8 3.8": ["prev"], "2.4 9.6 14.3": ["ventral"], "3.2 12.1 5.8": ["asceticism"], "-1.0 6.0 5.2": ["untraced"], "10.1 9.9 15.0": ["legerdemain"], "6.7 5.2 10.3": ["puttin"], "15.6 4.2 12.9": ["hefted"], "10.5 2.5 8.3": ["rejigging"], "3.3 11.3 5.4": ["magnetization"], "6.8 7.2 32.2": ["jackfruit"], "3.2 -6.9 7.6": ["certs"], "5.1 5.4 26.1": ["daiquiri"], "2.0 29.6 4.4": ["obscurantism"], "2.6 1.2 10.1": ["portlet"], "-2.5 14.0 10.4": ["pathogenicity"], "6.4 8.3 17.7": ["kobe"], "10.5 11.4 5.9": ["samsung"], "5.4 4.5 11.9": ["fairings"], "3.8 3.3 7.5": ["proprietress"], "9.2 14.1 2.0": ["inscribing"], "12.1 2.7 13.6": ["prizewinning"], "-0.0 5.2 -4.4": ["misplacement"], "0.6 2.9 0.9": ["ringfenced"], "-2.1 21.2 9.8": ["chokepoints"], "14.9 5.3 8.9": ["scribblers"], "-4.5 8.4 12.5": ["trampers"], "14.7 17.6 7.9": ["inadvertantly"], "0.5 18.4 16.1": ["defoliated"], "8.9 6.2 18.6": ["eric"], "-4.6 19.4 9.1": ["originalism"], "3.6 7.2 11.2": ["hermitage"], "19.9 12.2 15.3": ["schmucks"], "8.5 0.6 12.3": ["planemakers"], "3.8 0.9 8.2": ["sectioning"], "11.6 3.5 7.0": ["incubates"], "-2.8 5.7 20.0": ["purees"], "13.1 5.4 8.4": ["pitchside"], "1.5 9.3 17.6": ["sperms"], "-0.1 11.9 5.2": ["performative"], "-3.7 12.5 6.2": ["upselling"], "2.1 3.8 10.3": ["kegger"], "12.9 5.4 -0.3": ["ululating"], "-4.0 -3.0 0.2": ["qual"], "8.2 15.9 3.7": ["contriving"], "19.6 22.3 10.7": ["pickaxe"], "-2.2 21.7 6.0": ["gameplans"], "1.4 16.9 7.0": ["airlifter"], "1.1 10.8 25.3": ["bracts"], "8.0 13.3 5.2": ["dirtying"], "1.1 15.4 9.4": ["apprehends"], "-0.7 5.5 4.8": ["inkjets"], "5.4 -4.4 1.9": ["senor"], "9.7 -2.6 0.8": ["ona"], "-9.5 4.2 7.0": ["hcp"], "3.5 14.2 32.2": ["flatheads"], "12.3 8.1 7.3": ["sexily"], "1.2 7.6 -0.1": ["deservingly"], "6.9 6.9 21.7": ["coarsely"], "3.6 8.2 0.2": ["microsieverts"], "-0.2 18.6 8.7": ["casteism"], "8.5 11.5 2.8": ["utopias"], "7.8 6.2 6.6": ["megaresort"], "4.7 11.7 3.9": ["declination"], "-4.4 4.7 -2.9": ["prednisolone"], "10.2 29.4 22.6": ["minesweeper"], "-8.6 0.8 -1.9": ["laypersons"], "10.6 26.1 5.3": ["belligerently"], "3.3 24.3 14.8": ["platformers"], "5.6 7.9 9.3": ["slippy"], "-5.5 6.8 12.4": ["interclub"], "9.0 1.9 11.1": ["longhaired"], "-1.3 14.2 4.4": ["stigmatizes"], "-6.6 16.2 -2.1": ["counterespionage"], "4.8 25.2 7.1": ["deadliness"], "-0.8 14.0 3.2": ["compressive"], "5.4 6.6 6.2": ["freesheet"], "4.5 10.4 4.6": ["specced"], "-1.1 7.6 -0.4": ["equalizes"], "3.1 8.8 0.1": ["underfinanced"], "19.9 0.3 5.8": ["glitziest"], "7.0 -1.4 17.3": ["kong"], "0.9 -4.4 8.7": ["legals"], "16.8 6.1 3.9": ["moldering"], "6.5 5.1 38.8": ["maki"], "8.7 2.4 8.0": ["sheesh"], "19.1 10.3 9.0": ["clumpy"], "3.2 10.6 26.0": ["habanero"], "-3.2 5.7 11.3": ["dedupe"], "12.8 15.9 -0.3": ["unleased"], "-6.5 3.7 11.4": ["slowpitch"], "-3.3 -0.6 7.1": ["dzongkhag"], "0.4 10.6 16.3": ["adipex"], "-0.6 -2.3 9.9": ["biotin"], "-2.3 4.4 -7.3": ["annexure"], "4.8 26.2 2.8": ["intelligences"], "-5.1 4.5 7.3": ["recommencement"], "-4.6 7.0 10.0": ["exons"], "13.7 12.4 6.0": ["rapturously"], "8.1 6.8 7.0": ["thorugh"], "5.0 10.8 19.2": ["myrtle"], "2.3 10.1 -1.7": ["astrophysical"], "5.1 2.6 11.5": ["cmr"], "3.0 7.3 52.7": ["plaice"], "14.7 6.2 10.6": ["loll"], "-3.2 -1.0 18.7": ["oocyte"], "-1.4 11.2 13.0": ["launchings"], "1.5 9.9 2.5": ["capos"], "1.0 7.5 13.6": ["ong"], "6.9 17.4 12.5": ["nastily"], "14.8 14.6 7.8": ["enshrouded"], "6.5 11.2 0.4": ["hosannas"], "5.3 2.5 14.5": ["williams"], "1.8 3.8 10.0": ["commentated"], "-7.9 6.7 15.0": ["scatting"], "-5.4 28.1 11.7": ["playthrough"], "5.9 9.7 10.7": ["microscale"], "-2.1 8.0 3.4": ["effectivity"], "-7.6 13.1 2.9": ["refactoring"], "3.6 9.2 38.2": ["streamside"], "1.8 2.9 13.8": ["encaustic"], "-0.6 3.1 6.5": ["stayaway"], "1.6 7.3 16.7": ["croft"], "9.6 7.4 8.8": ["unscrewing"], "7.2 28.2 2.9": ["telekinesis"], "25.0 4.3 7.7": ["stonking"], "-4.4 7.4 14.6": ["ceramah"], "5.5 9.4 7.0": ["aggravations"], "13.9 6.1 6.2": ["papermaker"], "8.2 9.0 4.6": ["downsizings"], "4.4 5.0 13.3": ["ares"], "-2.3 12.5 4.3": ["unmediated"], "15.5 13.3 12.6": ["bumpkins"], "-3.6 10.5 1.7": ["offerors"], "-0.1 6.0 2.8": ["inclusively"], "9.8 6.2 15.1": ["cravat"], "15.0 7.3 12.2": ["gatecrashing"], "3.1 0.3 11.3": ["phytosanitary"], "-6.3 3.5 4.1": ["drivetrains"], "1.8 7.5 13.7": ["brazing"], "-6.2 2.9 9.3": ["rutile"], "6.2 0.7 16.4": ["thomas"], "-2.6 -0.2 4.5": ["kv"], "15.1 16.6 9.4": ["wormholes"], "8.1 3.4 13.2": ["cantilevers"], "4.3 8.8 5.9": ["chesting"], "-4.3 0.7 6.3": ["multiprocessing"], "6.8 9.0 12.6": ["nib"], "15.8 8.5 14.5": ["wingspans"], "2.7 2.3 9.5": ["archdioceses"], "10.8 12.1 7.5": ["subfolders"], "3.5 22.0 14.8": ["clansmen"], "7.7 1.8 12.4": ["nat"], "-12.0 14.1 1.3": ["paraphrases"], "-1.4 6.7 8.3": ["shiva"], "2.6 -0.0 6.6": ["seg"], "-5.7 4.8 5.2": ["modulus"], "2.4 2.0 10.9": ["decors"], "14.7 18.8 6.7": ["cabals"], "-10.4 4.9 -3.9": ["sequelae"], "-4.9 4.6 8.3": ["manufacturable"], "-7.1 0.2 7.6": ["recordation"], "8.6 6.4 4.1": ["kindles"], "3.9 6.9 6.0": ["somthing"], "10.1 5.8 6.4": ["ess"], "2.6 18.8 1.0": ["aggresive"], "16.8 4.3 29.8": ["ducky"], "4.0 14.7 -4.5": ["humanization"], "4.9 1.0 -4.6": ["monetizes"], "5.0 6.1 9.3": ["gridded"], "5.6 9.3 25.8": ["chitin"], "4.7 20.8 4.7": ["parallax"], "3.3 5.0 9.2": ["twd"], "2.7 5.8 5.8": ["jane"], "5.9 1.7 8.9": ["mc"], "13.0 0.7 11.9": ["stonemasons"], "1.6 17.2 17.7": ["dieback"], "7.4 7.0 11.0": ["gravitates"], "-2.0 4.1 3.5": ["myocarditis"], "-2.2 21.0 9.5": ["polarities"], "3.1 5.3 5.0": ["proctors"], "6.5 10.4 7.5": ["miscounted", "reprogramme"], "6.4 12.0 7.9": ["sodomize"], "11.8 3.3 14.7": ["pediment"], "-0.9 9.4 5.7": ["regift"], "9.1 12.9 1.7": ["handier"], "5.2 0.4 6.7": ["buss"], "-14.2 -0.5 5.6": ["doulas"], "10.0 15.0 8.6": ["kneejerk"], "6.7 2.3 -0.3": ["subleases"], "6.9 13.5 11.4": ["subgenres"], "5.6 -5.9 12.8": ["bookbinding"], "-2.0 5.0 7.4": ["renovator"], "-3.0 13.3 0.0": ["tankless"], "1.7 5.4 20.5": ["tenting"], "6.3 11.3 6.1": ["secretiveness"], "2.4 11.0 16.6": ["smartass"], "-1.8 6.6 -3.8": ["criminalises"], "4.7 0.4 29.5": ["menudo"], "5.6 3.9 11.7": ["ajb"], "-9.2 13.3 0.5": ["effectuated"], "2.2 7.7 13.8": ["babu"], "12.9 2.1 3.1": ["wheezed"], "6.2 6.4 11.0": ["diyas"], "-7.2 14.4 7.3": ["kins"], "17.1 7.4 11.4": ["deader"], "16.2 11.6 10.4": ["sleekness"], "18.5 -5.6 0.3": ["shopfronts"], "3.8 3.8 4.6": ["bpm"], "4.0 7.1 16.8": ["tuxedoes"], "7.6 8.3 11.4": ["stator"], "4.0 -3.1 7.7": ["reauthorizes"], "6.0 13.6 9.6": ["repubs"], "6.9 10.9 -3.9": ["instillation"], "12.0 7.8 18.0": ["microwavable"], "4.3 6.8 12.5": ["solidworks"], "3.0 6.9 8.5": ["stentorian"], "0.9 10.8 20.9": ["clovers"], "-7.2 12.5 -0.2": ["endocarditis"], "2.2 2.2 16.9": ["lapidary"], "4.5 11.4 14.3": ["phylogenetic"], "24.6 5.3 -0.0": ["telecomm"], "5.1 11.5 -8.1": ["thunderstruck"], "0.1 13.3 11.4": ["uncultivated"], "3.7 6.7 12.6": ["daguerreotype"], "6.4 0.0 9.8": ["sportscotland"], "-5.0 6.5 14.5": ["saprolite"], "10.0 14.2 12.6": ["conquistadors"], "1.6 5.2 9.5": ["reassembles"], "14.8 7.2 17.7": ["stripy"], "-1.2 -9.3 -2.5": ["rel"], "-10.8 8.9 3.9": ["decedents"], "0.3 0.4 6.5": ["outdrew"], "2.2 10.4 3.8": ["musics"], "9.3 10.1 9.4": ["gibes"], "-1.4 14.3 8.5": ["consistantly"], "5.0 30.7 17.9": ["quartering"], "2.9 3.6 12.0": ["bustline"], "1.2 12.4 12.0": ["kya"], "11.3 8.5 20.6": ["sandcastles"], "2.2 12.7 12.8": ["trippin"], "0.4 11.3 13.9": ["labelmate"], "11.7 17.1 14.0": ["spitter"], "15.6 12.6 7.2": ["boggling"], "-0.2 15.9 0.8": ["overstretching"], "10.9 1.6 3.8": ["fait"], "29.8 22.9 26.9": ["centipedes"], "3.9 -6.7 18.4": ["scrapings"], "10.9 9.9 7.8": ["occassional"], "12.8 6.0 16.2": ["spooled"], "-0.4 2.9 6.3": ["walkup"], "1.0 7.0 15.2": ["tarot"], "11.5 5.5 8.9": ["gild"], "-1.1 3.2 1.6": ["asthenia"], "4.9 -2.0 12.6": ["isang"], "1.9 6.5 5.0": ["stocktaking"], "5.2 11.2 16.6": ["ashy"], "15.6 0.0 7.6": ["sleekly"], "5.5 7.6 13.2": ["distributional"], "4.7 4.9 9.2": ["upsize"], "1.8 4.1 4.5": ["antiperspirant"], "-3.5 -0.2 5.9": ["adiposity"], "-2.5 13.3 10.0": ["sovereigntists"], "3.2 12.3 17.2": ["kiting"], "0.5 10.3 5.6": ["subtexts"], "24.8 14.2 1.9": ["omni"], "-4.0 -1.1 9.8": ["watermain"], "4.9 7.3 7.8": ["extractable"], "6.7 -2.5 20.1": ["partyers"], "-0.4 16.2 4.7": ["possessiveness"], "5.8 18.9 7.8": ["containable"], "9.1 6.9 14.1": ["grippers"], "-4.8 34.8 -1.7": ["fidayeen"], "3.0 7.5 14.2": ["metabolisms"], "10.0 7.9 6.4": ["kiddingly"], "1.7 11.9 7.3": ["inactivating"], "2.8 3.7 9.8": ["psychotropic"], "2.6 9.4 6.1": ["prehypertension"], "6.8 16.7 -3.9": ["hitlist"], "-11.7 -3.6 1.5": ["aripiprazole"], "4.6 4.1 12.0": ["jlc"], "4.4 11.0 8.3": ["suburbanization"], "6.1 2.1 18.1": ["tinplate"], "8.3 8.8 2.3": ["conurbation"], "-6.0 5.6 15.5": ["mannerly"], "4.1 -2.7 2.1": ["ich"], "15.7 7.3 14.8": ["deliverymen"], "3.0 15.7 6.0": ["allusive"], "4.9 7.8 6.3": ["victimless", "custo"], "-1.6 2.8 7.3": ["gassers"], "-0.8 -1.5 8.6": ["platting"], "9.2 7.0 15.6": ["fluttery"], "7.5 6.4 30.3": ["bouillon"], "9.7 9.4 15.4": ["lancing"], "-3.0 15.3 0.3": ["epitaphs"], "15.3 13.6 2.5": ["convulse"], "4.6 19.4 2.5": ["polities"], "11.6 2.3 9.2": ["cokes"], "4.7 0.7 8.4": ["spic"], "-2.2 5.6 14.2": ["traceback"], "9.9 3.3 8.3": ["eagling"], "0.3 2.9 10.5": ["herbals"], "-1.2 3.7 5.0": ["calcifications"], "7.6 34.0 9.0": ["outthink"], "-1.9 4.9 10.2": ["naka"], "14.3 11.7 16.1": ["jousts"], "4.9 7.2 11.1": ["anamorphic"], "-1.9 8.7 2.7": ["handballed"], "17.9 5.0 9.5": ["gangling"], "9.3 5.3 3.5": ["overenthusiastic"], "1.3 8.5 11.3": ["positivism"], "14.8 11.4 16.4": ["mammy"], "5.9 13.8 26.6": ["planer"], "13.0 10.8 14.7": ["crescents"], "-1.5 11.5 5.1": ["overcommitted"], "3.6 2.5 6.8": ["musos"], "4.2 -2.5 8.5": ["jammin"], "2.7 1.1 20.7": ["amaretto"], "16.1 -5.7 5.8": ["dusters"], "21.1 18.6 7.7": ["dimwits"], "10.4 15.8 15.1": ["tempests"], "3.5 16.8 6.3": ["predicable"], "-7.1 19.4 5.9": ["oxidants"], "-4.2 19.4 15.4": ["geocachers"], "3.2 6.4 -1.0": ["congest"], "-0.3 2.1 3.8": ["glycine"], "5.3 3.0 10.3": ["impounds"], "9.0 11.7 21.4": ["jew"], "-8.3 -2.1 5.3": ["encashed"], "-1.0 13.4 -2.7": ["traumatising"], "7.9 2.5 6.2": ["howdy"], "8.6 22.4 8.1": ["bloodbaths"], "-2.3 10.2 3.3": ["unprofessionally"], "18.0 4.2 7.7": ["iin"], "-5.8 1.1 5.3": ["grayshirt"], "7.8 13.5 8.9": ["doorframe"], "10.3 0.0 -0.2": ["reknowned"], "-2.2 0.4 2.1": ["ashrams"], "3.2 16.0 16.2": ["phages"], "1.5 24.9 2.0": ["intensions"], "-8.8 -3.2 5.7": ["neurodevelopmental"], "1.2 8.6 13.6": ["tappers"], "3.9 5.9 28.1": ["pitas"], "-2.1 9.8 4.5": ["ingrain"], "11.4 10.5 2.4": ["stong"], "-0.2 10.2 5.8": ["bencher"], "-3.3 3.5 19.0": ["enders"], "5.2 2.5 12.0": ["punkers"], "16.7 -0.7 12.4": ["santa"], "-0.4 3.4 7.8": ["webcomics", "redeposit"], "19.2 7.5 6.0": ["backdropped"], "-1.8 14.9 18.2": ["anchorages"], "3.3 -1.0 4.1": ["amatuer"], "16.2 22.7 4.3": ["skulk"], "7.6 8.7 6.5": ["patroness"], "2.1 20.1 11.5": ["vampirism"], "-4.7 8.2 13.0": ["chlorpyrifos"], "-4.0 1.9 10.4": ["biodegradation"], "-5.0 2.4 7.8": ["infrequency"], "14.8 8.0 5.7": ["bub"], "6.8 4.0 3.0": ["osmotic"], "-11.5 -4.3 -2.1": ["rehabilitations"], "8.9 -0.2 5.6": ["ids"], "-0.2 4.4 7.9": ["lari"], "2.7 20.3 -2.6": ["thinkable"], "3.5 10.4 10.9": ["kneepads"], "1.2 12.2 34.9": ["wildfowl"], "-4.0 6.4 2.2": ["vasopressin"], "8.0 9.5 5.9": ["italic"], "1.7 1.9 18.5": ["seersucker"], "5.5 1.6 15.2": ["raffish"], "3.0 13.9 10.7": ["fisting"], "-5.1 8.1 2.8": ["midscale"], "22.5 13.6 0.5": ["whirr"], "11.6 14.4 4.7": ["petulantly"], "-0.5 11.7 2.7": ["lense"], "21.1 6.6 9.3": ["dozy"], "3.7 14.5 11.2": ["makeable"], "1.0 6.3 4.6": ["collabo"], "16.6 17.0 4.9": ["obliviously"], "5.1 2.1 13.3": ["radiocarbon"], "-1.4 2.6 11.6": ["limericks"], "-3.8 11.5 7.5": ["ostracizing"], "8.1 8.7 15.5": ["beamer"], "5.9 7.3 6.2": ["abou"], "-3.0 3.9 2.1": ["cfm"], "1.7 4.2 7.4": ["sentimentally"], "11.5 14.2 19.3": ["dunkers"], "6.9 16.3 5.8": ["controled"], "6.8 1.6 2.8": ["handholding"], "3.1 2.5 7.3": ["sidecars"], "15.8 7.6 8.5": ["jiggy"], "4.1 4.6 8.7": ["nightstands"], "9.9 7.4 18.7": ["supes"], "17.8 8.2 9.8": ["clunking"], "9.7 6.9 11.0": ["cubbyhole"], "5.8 12.4 13.5": ["ahistorical"], "1.3 14.9 14.6": ["gybed"], "6.2 5.7 14.7": ["hangnail"], "6.6 -2.0 5.0": ["unspooling"], "7.1 11.8 8.1": ["heliosphere"], "-2.8 15.4 5.0": ["originalist"], "12.7 5.7 3.8": ["doodled"], "4.5 -4.7 4.5": ["toa"], "3.7 9.9 6.0": ["hangups"], "-1.5 3.9 6.6": ["ferroelectric"], "-2.6 10.1 10.6": ["enfranchisement"], "-10.7 8.0 0.4": ["actioned"], "22.0 15.2 6.0": ["guzzler"], "8.9 3.2 3.9": ["rummaged"], "2.0 7.8 -4.3": ["telex"], "12.1 -3.2 15.2": ["grommet"], "-0.1 5.4 11.1": ["malapropisms"], "3.2 16.2 0.4": ["militantly"], "14.0 4.2 -0.7": ["distributer"], "2.8 12.0 9.6": ["dar"], "-4.4 18.0 17.3": ["bowhunter"], "0.6 5.8 33.2": ["adobo"], "5.6 4.4 2.2": ["benchwarmer"], "5.0 18.0 8.2": ["midfields"], "3.4 10.8 14.4": ["dinking"], "-3.5 8.1 7.9": ["pegmatites"], "7.0 14.3 21.7": ["impala"], "5.7 5.5 7.2": ["priestesses", "retore"], "-5.6 8.1 2.2": ["domiciliary"], "8.1 5.8 17.7": ["circumpolar"], "10.5 20.8 13.4": ["whup"], "-0.4 3.7 26.6": ["containership"], "2.0 16.9 7.1": ["superposition"], "9.0 11.9 9.2": ["spookiest"], "-5.7 10.6 8.2": ["vasculitis"], "5.3 9.3 1.6": ["deconsolidated"], "-14.3 19.7 6.1": ["chemotherapeutic"], "-0.7 -2.8 33.4": ["pecorino"], "12.9 13.4 12.5": ["tootsies"], "-2.2 4.4 -0.6": ["homeopath"], "4.7 1.4 9.3": ["characterful"], "-0.9 6.3 5.3": ["trepidations"], "5.1 7.9 4.5": ["replications"], "-0.2 1.4 3.8": ["liveblogging"], "13.2 10.0 13.2": ["chimeras"], "1.2 1.7 6.4": ["triallist"], "12.8 3.7 10.6": ["underpricing"], "-2.0 6.5 11.6": ["drunker"], "-1.2 5.8 0.8": ["mathematic"], "-1.2 9.2 9.0": ["rolodex"], "4.4 -0.8 -0.1": ["daugher"], "14.3 6.0 9.8": ["inkwell"], "13.0 10.2 14.3": ["thew"], "-0.2 -0.2 6.0": ["excommunications"], "12.8 0.6 2.5": ["plasticky"], "-1.8 -1.8 -0.4": ["prostaglandin"], "3.0 11.6 7.6": ["airily"], "-2.9 8.2 4.0": ["fazes"], "-3.6 6.5 2.6": ["forenoon"], "13.3 2.7 16.2": ["tuxedoed"], "17.9 12.5 12.6": ["fetishist"], "5.4 3.3 4.2": ["cosmologist"], "19.1 0.4 17.3": ["piddly"], "10.1 3.9 1.9": ["perturbing"], "-5.4 8.4 5.1": ["depressants"], "3.9 12.6 6.4": ["castigation"], "4.1 11.9 13.0": ["refreezes"], "-1.5 4.7 4.1": ["transmedia"], "4.3 9.9 19.4": ["larks"], "8.0 3.2 19.3": ["dowel"], "16.4 16.7 15.1": ["phisher"], "10.3 26.4 5.2": ["frontally"], "5.2 19.0 14.3": ["gamebreaker"], "-1.5 10.5 11.2": ["nutritive"], "3.6 1.1 6.0": ["partaken"], "1.2 42.7 4.5": ["fedayeen"], "5.2 2.5 0.7": ["tthe"], "3.2 17.6 5.9": ["demagogy"], "7.4 16.0 8.6": ["allover"], "8.2 16.3 11.3": ["hoeing"], "-2.5 11.2 -0.1": ["unleveraged"], "5.9 12.0 12.3": ["highness"], "0.2 6.7 16.2": ["cava"], "3.7 6.8 23.1": ["outboards"], "3.6 4.3 11.5": ["punning"], "6.7 4.8 27.9": ["crockpot"], "-8.4 -3.8 5.9": ["introducers"], "2.9 20.1 8.0": ["supremacists"], "1.4 -4.2 4.4": ["tive"], "-3.8 9.0 1.1": ["decompressing"], "-1.8 10.6 6.6": ["whispery"], "9.3 11.7 13.3": ["infields"], "4.8 9.7 5.7": ["aerotropolis"], "19.8 1.7 19.9": ["placemat"], "9.7 -0.4 12.6": ["sweatsuit"], "-2.0 4.2 4.5": ["landmarking"], "14.3 8.5 7.5": ["pulping"], "-2.9 5.0 14.6": ["molybdenite"], "5.5 1.4 23.2": ["topaz"], "1.7 5.3 21.0": ["glassblowing"], "-1.2 -0.7 10.5": ["craniofacial"], "7.3 8.2 4.8": ["crossborder"], "4.4 5.3 0.5": ["succes"], "12.2 7.5 7.6": ["sloppiest"], "6.5 10.9 15.4": ["dishwater"], "-7.7 0.4 2.1": ["patency"], "3.4 6.9 33.6": ["mochi"], "8.7 3.5 -0.3": ["abertis"], "-0.4 4.1 1.6": ["introducer"], "11.3 0.2 9.0": ["bluechips"], "14.6 9.3 12.3": ["stomper"], "-7.4 5.3 18.1": ["wheats"], "8.1 -2.1 16.7": ["kicky"], "-5.2 13.6 0.2": ["armamentarium"], "-15.2 6.5 3.7": ["platooned"], "-3.0 5.3 11.7": ["disenfranchises"], "7.2 16.8 0.9": ["balkanized"], "15.3 12.9 7.5": ["scamsters"], "3.8 5.3 9.9": ["ome"], "-3.4 18.4 -0.5": ["radicalise"], "3.4 11.9 4.3": ["vacuity"], "12.0 1.3 11.5": ["zither"], "-2.3 15.4 4.9": ["remonstrance"], "-2.2 1.5 3.3": ["psychosexual"], "2.8 12.4 -0.9": ["militates"], "10.8 3.5 10.0": ["molder"], "-5.0 16.2 7.1": ["cohabitant"], "8.2 4.3 16.2": ["mohawks"], "-3.4 6.0 12.1": ["zari"], "-5.5 14.3 4.0": ["ethnical"], "2.7 5.1 14.6": ["fretwork"], "17.4 2.2 10.6": ["eon"], "1.7 4.6 9.0": ["priory"], "7.4 6.5 1.3": ["fessing"], "-2.0 13.3 7.7": ["remarries"], "9.2 11.5 6.1": ["fluoresce"], "4.4 12.2 17.4": ["coli"], "9.0 6.6 0.1": ["fetishistic"], "3.4 13.9 1.6": ["misguidedly"], "20.5 -0.5 10.2": ["twinkly"], "6.5 4.6 50.5": ["groupers"], "1.4 16.4 10.6": ["licentiousness"], "4.4 33.8 4.9": ["supervillains"], "2.9 3.0 -0.4": ["sublingual"], "6.6 14.3 10.1": ["twain"], "7.5 4.8 12.0": ["fusses"], "3.8 3.5 6.7": ["stylin"], "-4.4 4.5 12.5": ["overcrowd"], "3.1 5.6 -0.5": ["chartbusters", "racewinner"], "-3.8 13.3 0.3": ["particularized"], "5.4 14.0 7.7": ["dribblers"], "-4.8 8.4 3.9": ["adenoids"], "3.9 18.5 16.8": ["bacteriophage"], "7.7 2.5 20.7": ["nougat"], "11.7 17.1 12.3": ["irradiate"], "6.9 7.9 5.3": ["provident"], "10.6 20.8 5.3": ["telepathically"], "0.3 -4.9 14.0": ["yarding"], "8.0 3.9 12.5": ["rfw"], "-7.0 6.8 3.0": ["supplementaries"], "3.1 0.3 16.8": ["longhouses"], "17.0 12.7 1.8": ["haughtily"], "-2.3 12.1 10.6": ["downhiller"], "2.8 11.2 7.7": ["bibliophiles"], "2.5 21.6 22.0": ["mockingbirds"], "-9.2 1.2 -3.2": ["committments"], "17.1 4.9 7.2": ["squarish"], "11.6 7.2 10.4": ["necking"], "4.4 -4.1 10.0": ["tay"], "9.7 9.8 7.6": ["mousing"], "13.4 15.3 2.7": ["wretchedly"], "2.0 -2.5 1.8": ["nn"], "2.5 3.4 8.7": ["chaperon"], "-3.7 1.5 5.1": ["millirems"], "3.5 3.8 4.1": ["microinsurance"], "-4.7 0.2 11.1": ["perfs"], "3.4 22.3 5.2": ["servility"], "4.5 1.6 3.3": ["tracings"], "9.1 16.1 9.7": ["cataclysms"], "4.3 8.8 7.4": ["seances"], "8.0 5.2 10.7": ["racin"], "-6.1 2.0 4.3": ["handpiece"], "0.6 2.7 3.6": ["recommissioned"], "6.0 5.9 18.3": ["ovum"], "2.6 23.6 5.1": ["nonconventional"], "10.1 11.3 -1.5": ["hushing"], "3.3 10.9 7.8": ["primatologist"], "11.4 10.9 1.9": ["synergetic"], "9.5 13.6 16.0": ["puritans"], "6.3 15.9 24.1": ["bracken"], "5.8 0.5 22.1": ["formalin"], "1.7 7.9 5.3": ["mandir"], "-2.9 3.3 11.7": ["epitaxial"], "12.2 2.4 12.0": ["chancers"], "-1.6 13.1 5.2": ["gainsaying"], "-5.6 12.4 8.8": ["pillion"], "9.7 0.2 3.3": ["poky"], "-3.3 0.7 6.6": ["bandleaders"], "3.2 -3.5 25.3": ["foodbank"], "17.9 -5.5 0.2": ["spruik"], "2.2 13.3 5.0": ["metasearch"], "31.8 5.9 2.2": ["comapny"], "10.1 9.8 9.4": ["anagrams"], "23.7 -1.0 11.6": ["bluechip"], "14.0 9.4 30.0": ["budgie"], "-2.7 13.5 13.2": ["kayo"], "10.1 18.9 11.2": ["utopianism"], "3.5 2.2 8.8": ["mannish"], "6.6 9.7 1.7": ["dematerialized"], "-3.8 7.0 0.8": ["softphones"], "0.1 6.9 5.7": ["dysfunctionality"], "15.9 23.1 5.5": ["superpowered"], "-0.9 1.7 -3.4": ["averagely"], "17.5 17.2 11.0": ["mirages"], "-9.2 3.8 9.8": ["magistracy"], "5.2 3.1 6.8": ["epitomizing"], "19.1 1.3 9.0": ["cloggers"], "0.8 0.6 -0.9": ["provosts"], "14.4 15.7 3.3": ["hacktivists"], "-0.5 12.3 4.6": ["refudiate"], "1.7 11.2 3.0": ["unaccountability"], "8.8 9.2 6.4": ["callin"], "1.5 14.4 10.8": ["bureaucratically"], "12.8 20.0 5.6": ["whacko"], "4.0 3.5 7.3": ["druggists"], "5.9 3.6 9.3": ["biddings"], "18.3 13.8 14.6": ["hexagons"], "17.9 8.1 3.6": ["countersuits"], "-1.6 9.0 21.7": ["unharvested"], "2.7 8.6 33.4": ["kumquat"], "-0.1 7.0 5.8": ["neurochemical"], "24.4 22.4 28.0": ["beastie"], "1.7 4.2 4.3": ["preclearance"], "3.7 9.5 7.4": ["quizmaster"], "12.8 7.9 35.0": ["clownfish"], "9.6 4.5 13.2": ["showgoers"], "-1.4 7.7 6.7": ["std"], "13.4 18.7 22.6": ["tusker"], "-2.4 2.5 19.8": ["parimutuel"], "8.5 13.4 6.7": ["logarithmic"], "3.6 4.1 -1.8": ["develope"], "6.0 7.8 14.8": ["sandhills"], "10.3 -0.6 35.1": ["souvlaki"], "13.2 7.3 10.2": ["slashdot"], "10.6 6.3 8.8": ["planetariums"], "-8.0 0.9 11.6": ["interpellation"], "11.7 20.1 35.8": ["landlubbers"], "2.1 1.1 45.2": ["ahi"], "4.7 5.5 9.4": ["teahouses"], "-5.8 4.9 8.2": ["endometrial"], "3.7 10.8 3.6": ["virologists"], "4.6 4.8 12.1": ["eyelets"], "4.7 3.3 0.4": ["hypo"], "-5.9 -6.3 12.8": ["lm"], "-3.6 13.2 12.7": ["adverbs"], "6.3 4.3 37.7": ["ragout"], "-3.9 5.6 11.6": ["impetigo"], "10.2 18.6 16.7": ["sliming"], "6.9 2.7 15.6": ["sean"], "9.0 5.1 12.2": ["diddly"], "11.7 12.9 16.6": ["obelisks"], "5.4 11.8 7.0": ["envying"], "-0.5 -5.1 0.5": ["grafs"], "10.2 15.0 8.6": ["breastplate"], "4.8 11.0 8.1": ["wakened"], "1.0 -1.1 2.3": ["suppl"], "1.6 7.7 7.2": ["tehsildar"], "8.1 0.8 18.9": ["creekside"], "-0.3 10.1 14.5": ["fracing"], "-1.1 11.4 23.9": ["gravies"], "3.3 3.1 36.0": ["moussaka"], "-0.2 8.3 5.5": ["homesteader"], "-0.5 0.3 5.6": ["reupholstered"], "12.2 14.4 9.1": ["snidely"], "11.4 8.2 5.7": ["photosensitive"], "3.9 8.2 -6.5": ["seperation"], "0.5 -2.2 8.1": ["plasticizer"], "8.0 -2.7 13.9": ["bodhran"], "8.2 7.3 4.6": ["recapitalising"], "7.8 16.1 7.1": ["subdues"], "5.0 3.9 8.2": ["frontend"], "7.7 3.2 12.2": ["divan"], "-5.9 6.3 5.3": ["telbivudine"], "-2.4 5.1 22.5": ["stumpage"], "0.2 8.8 2.1": ["chosing"], "7.5 0.9 10.5": ["jlw"], "8.6 4.8 5.5": ["picnicked"], "-1.3 3.3 12.1": ["biostatistician"], "-1.5 1.5 0.5": ["pd"], "2.4 0.4 10.6": ["facially"], "-0.7 7.7 3.1": ["longitudinally"], "-2.0 2.5 8.5": ["gomembers"], "-11.2 2.8 16.1": ["sangiovese"], "-3.7 10.4 10.0": ["graveled"], "4.1 4.9 4.0": ["civils"], "7.9 11.3 13.9": ["wiseguys"], "-3.1 17.8 9.4": ["dichotomous"], "13.8 21.7 16.8": ["spinmeisters"], "4.7 12.8 11.0": ["clasico"], "-6.4 -1.2 7.7": ["footnoted"], "-4.7 9.4 -2.5": ["wef"], "8.6 24.8 10.9": ["defang"], "4.5 4.5 15.1": ["ocelot"], "14.6 3.4 11.1": ["cryogenics"], "3.5 8.6 13.5": ["daybed"], "6.5 22.7 9.3": ["yeller"], "-4.9 -3.8 4.7": ["microenterprise"], "10.3 8.7 14.4": ["sods"], "-0.8 6.1 7.3": ["vitreous"], "5.3 14.6 18.4": ["sinfully"], "1.0 9.7 6.2": ["peeves"], "-3.7 6.9 0.7": ["antiplatelet"], "-4.0 9.2 3.1": ["walkabouts"], "6.4 8.7 10.0": ["gnash"], "11.5 14.1 7.4": ["plodder"], "4.4 18.8 7.1": ["homefield"], "6.3 9.5 4.5": ["maladjusted"], "10.8 6.0 9.4": ["bottomlines"], "-0.2 16.8 14.3": ["interconference"], "4.7 16.4 7.2": ["interferometer", "willpc"], "15.7 19.6 14.7": ["sickles"], "-1.8 2.8 -1.5": ["recoding"], "13.6 6.2 5.4": ["satcaster"], "9.0 4.6 1.4": ["wising"], "0.5 6.9 5.7": ["misimpression"], "3.8 8.5 2.0": ["subscale"], "7.5 6.9 37.7": ["leatherback"], "10.7 9.2 6.7": ["outracing"], "7.1 10.6 11.0": ["rationalists"], "-0.3 3.3 13.0": ["rerunning"], "7.1 2.2 6.6": ["dirges"], "12.3 4.1 22.7": ["dinette"], "15.0 7.6 7.2": ["maharaja"], "2.3 10.0 11.4": ["elims"], "1.8 11.5 6.1": ["misdirecting"], "5.8 13.2 6.8": ["dully"], "6.1 19.9 9.2": ["newsok"], "20.8 4.6 21.9": ["pillowy"], "5.3 3.2 13.6": ["scorecarding"], "0.2 20.4 3.5": ["balkanization"], "2.1 -0.1 8.3": ["slurries"], "11.7 14.9 8.8": ["petrodollar"], "9.6 5.1 9.1": ["spinsters"], "13.0 11.4 12.4": ["unimposing"], "-14.0 2.8 12.7": ["bottlings"], "12.5 17.3 7.0": ["beholding"], "9.1 7.2 14.6": ["chocoholics"], "-5.7 6.0 1.8": ["escitalopram"], "3.1 1.6 10.4": ["hae"], "9.4 8.7 -4.2": ["thei"], "5.4 11.2 8.8": ["swellings"], "5.0 7.0 9.0": ["titter"], "16.9 19.2 6.0": ["wielders"], "10.3 4.2 11.6": ["blokey"], "-4.0 3.6 4.6": ["challaned"], "5.7 8.6 2.7": ["paradigmatic"], "-0.9 4.5 7.9": ["neuroendocrine"], "5.3 2.2 7.4": ["arbitrating"], "-5.9 1.9 5.4": ["helmers"], "-4.2 9.6 6.6": ["decluttering"], "13.2 -4.2 11.3": ["glitzier"], "-1.3 0.9 11.3": ["bumiputera"], "15.2 7.8 18.6": ["iceman"], "6.3 5.1 22.0": ["kelly"], "10.3 4.6 2.4": ["quater"], "3.2 3.5 3.3": ["uploader"], "5.8 4.8 16.4": ["mahout"], "-4.6 10.6 2.5": ["pleasantness"], "8.9 11.3 3.9": ["bides"], "7.9 5.6 8.8": ["spanners"], "-6.2 14.1 12.8": ["ippon"], "6.7 11.4 10.7": ["reacquaint"], "2.2 1.3 9.6": ["dollarisation"], "7.6 0.8 11.5": ["bidi"], "2.6 -0.0 -6.8": ["arbitral"], "7.9 0.7 5.8": ["townhall"], "5.4 8.3 4.3": ["docility"], "6.0 4.2 8.4": ["sinecure"], "8.0 12.7 8.0": ["judder"], "4.8 1.9 18.6": ["lowrider"], "-6.7 2.1 8.9": ["passholders"], "6.6 9.5 1.4": ["precession"], "-1.6 8.8 18.2": ["ppv"], "-0.1 10.1 5.6": ["couturiers"], "16.1 -0.2 26.9": ["goopy"], "2.5 13.7 16.9": ["birdwatcher"], "4.0 4.7 5.0": ["freshens"], "16.1 2.3 9.4": ["runneth"], "5.7 8.3 5.8": ["kinematics"], "19.7 6.2 11.9": ["birdlike"], "-5.7 8.5 9.8": ["hypoglycemic"], "7.0 15.3 9.1": ["cuckolded"], "-1.4 10.9 -0.6": ["preachings"], "-5.9 13.1 2.2": ["epratuzumab"], "-2.6 9.3 11.1": ["confinements"], "15.1 5.4 11.5": ["shovelful"], "2.7 8.1 9.3": ["cethromycin"], "9.0 14.5 12.9": ["timorous"], "4.1 20.8 9.1": ["perpetrates"], "-2.9 6.0 12.3": ["bock"], "-0.6 3.8 5.0": ["underspend"], "0.7 9.4 6.0": ["multiband"], "-1.4 -3.1 16.2": ["quinceanera"], "-4.6 17.8 -0.3": ["oppositionist"], "1.4 6.0 6.7": ["vfx"], "-0.9 9.3 8.2": ["treasuring"], "16.8 17.3 10.6": ["monocle"], "2.4 7.7 7.1": ["nymphomaniac"], "6.0 4.0 10.0": ["puttered"], "11.5 10.9 9.5": ["pees"], "-7.9 7.8 -0.3": ["tiotropium"], "5.6 9.0 7.9": ["halfs"], "-4.1 4.8 2.2": ["tracheostomy"], "9.6 1.7 9.4": ["bentonite"], "15.4 15.9 8.6": ["cybersquatters"], "14.1 4.8 6.8": ["pensively"], "-2.7 6.9 11.5": ["enology"], "4.4 22.2 6.5": ["unrevealed"], "13.5 7.1 1.6": ["megatrends"], "-6.8 2.9 -0.2": ["conclusory"], "3.5 7.4 -0.9": ["gipsies"], "12.1 -1.9 17.5": ["pouf"], "-10.2 7.4 1.4": ["triptans"], "1.1 6.3 17.1": ["amparo"], "-4.5 17.4 3.1": ["discourtesy"], "1.6 1.2 28.1": ["aubergines"], "-0.0 11.4 6.3": ["partys"], "4.6 2.9 11.7": ["shoemaking"], "5.8 6.1 1.1": ["transcribes"], "2.4 7.4 2.4": ["reorganisations"], "4.5 11.1 16.6": ["clomid"], "-3.9 0.3 11.3": ["premixed"], "3.0 7.0 3.5": ["ack"], "14.0 6.5 2.3": ["commoditisation"], "6.8 7.6 34.1": ["wharfs"], "10.7 -2.6 16.9": ["insets"], "-10.7 10.5 8.4": ["chlorides"], "4.0 12.1 0.0": ["rewinds"], "-0.2 9.3 8.0": ["fishtailing"], "-8.3 7.7 6.7": ["shrillness"], "-9.3 7.9 14.5": ["liming"], "-4.9 6.0 22.3": ["bajra"], "-3.2 14.3 5.3": ["pharmacologically"], "3.7 7.6 18.9": ["timbering"], "5.5 5.9 7.4": ["diptych"], "12.8 11.2 7.1": ["reconfigures"], "-1.5 13.4 7.1": ["catchiness"], "5.0 22.4 0.7": ["unalienable"], "-0.1 20.4 17.8": ["chinlock"], "5.8 6.8 10.8": ["threequarters"], "-1.6 3.0 9.6": ["turnpikes"], "-2.0 2.6 9.2": ["vist"], "3.9 23.2 5.9": ["chauvinists"], "2.1 22.2 3.6": ["circumscribe"], "0.9 8.1 32.1": ["hominy"], "3.5 8.9 9.4": ["ren"], "4.5 12.9 4.1": ["outrace"], "0.9 9.1 23.7": ["rhizome"], "2.8 1.7 16.8": ["chuan"], "3.1 8.1 5.6": ["summitry"], "6.3 14.6 18.4": ["colloquialism"], "2.2 9.6 0.6": ["penalities"], "13.8 14.1 7.4": ["hillocks"], "-0.4 8.1 10.7": ["prostates"], "7.5 6.9 16.0": ["biodiverse"], "7.2 17.6 3.5": ["acquiescent"], "7.8 14.2 6.2": ["outhustling"], "5.6 11.4 9.8": ["etches"], "5.3 8.5 2.9": ["mick"], "7.9 6.6 -4.8": ["postulating"], "19.6 8.6 26.0": ["galleon"], "7.9 5.5 13.6": ["slops"], "-10.6 15.6 5.8": ["preseasons"], "16.3 8.0 14.1": ["dasher"], "2.2 3.3 4.4": ["ebookers"], "7.9 4.8 -1.0": ["sidenote"], "-3.7 11.2 10.3": ["ordains"], "0.8 35.7 7.2": ["taliban"], "9.4 7.0 11.2": ["madame"], "19.0 7.6 17.1": ["shiploads"], "0.6 5.3 3.6": ["sexcapades"], "4.2 10.6 5.8": ["datelined"], "15.7 7.6 13.3": ["manacles"], "-1.4 9.8 7.7": ["aptamers"], "8.4 7.0 6.0": ["alphabetic"], "9.1 1.6 5.8": ["clothiers"], "10.4 0.7 -4.0": ["divesture"], "-0.5 21.5 1.7": ["retributive"], "-1.8 8.8 3.9": ["commissionerate"], "6.5 -2.6 10.0": ["chinchillas"], "1.9 -0.4 8.7": ["reliquary"], "15.1 11.6 8.9": ["videogaming"], "9.4 20.2 4.3": ["bewilder"], "4.5 9.6 21.5": ["lakebed"], "0.3 4.4 19.3": ["refreezing"], "2.0 6.1 8.1": ["changelog"], "-5.4 18.5 19.0": ["bolls"], "-2.8 2.8 12.3": ["kaftans"], "-3.2 -2.2 1.9": ["receiverships"], "3.7 -3.5 4.4": ["fairtrade"], "21.6 10.9 7.3": ["rollercoasters"], "-9.3 14.5 16.6": ["cyclamen"], "4.6 5.3 16.4": ["healthfulness"], "5.6 21.4 18.9": ["briars"], "-1.1 5.3 14.6": ["snowcat"], "10.3 33.1 9.5": ["evilness"], "-0.3 7.7 4.7": ["wud"], "2.8 12.2 9.7": ["atenolol"], "10.9 10.9 14.5": ["hammerlock"], "6.1 0.3 0.8": ["multiformat"], "-5.9 3.4 -1.5": ["bizhub"], "8.4 22.2 1.2": ["deceitfully"], "9.2 21.9 14.8": ["cheesehead"], "13.7 -1.4 -1.6": ["vamped"], "6.0 7.9 0.5": ["unchallenging"], "-0.6 7.0 0.7": ["accomodating"], "9.2 2.0 16.6": ["waifs"], "11.4 10.9 26.4": ["latke"], "-1.0 4.6 16.0": ["jodhpurs"], "8.8 13.3 22.7": ["corgis"], "13.3 18.4 13.5": ["deforms"], "5.3 1.4 5.0": ["numbingly"], "-0.4 3.5 12.2": ["luthier"], "16.3 15.6 12.9": ["kaboom"], "11.3 8.9 8.3": ["gaggles"], "8.1 6.8 7.2": ["redeveloper"], "-7.8 13.0 7.9": ["careerism"], "3.8 9.7 5.3": ["wheedle"], "8.3 -4.0 3.9": ["prix"], "1.1 4.1 16.4": ["transcriptome"], "0.6 -3.8 8.0": ["vox"], "18.7 15.1 10.2": ["simulacrum"], "20.0 14.1 11.2": ["loudmouthed"], "-4.2 0.1 2.2": ["osteopathy"], "6.0 -1.0 5.4": ["decant"], "15.3 9.6 11.0": ["mountable"], "0.9 15.3 6.2": ["iconoclasm"], "-2.2 19.0 7.6": ["jailor"], "-8.6 9.9 -2.8": ["equivocated"], "9.4 5.7 11.0": ["screwup"], "2.2 4.1 5.9": ["spendings"], "-3.0 0.3 4.6": ["eculizumab"], "8.3 9.7 12.2": ["sprockets"], "-1.0 -1.1 9.3": ["cattery"], "-9.7 3.6 16.2": ["neutrophil"], "4.5 -7.2 -2.1": ["ven"], "-1.1 7.2 8.3": ["isolator"], "7.8 12.1 14.7": ["workingman"], "-1.5 7.2 5.5": ["abit"], "2.9 7.0 5.2": ["incarcerates"], "4.9 -3.3 -0.4": ["keynoted"], "6.2 1.1 7.3": ["overbid"], "17.9 18.7 4.8": ["exploiter"], "4.7 10.1 13.1": ["sensually"], "3.9 4.4 10.1": ["samiti"], "2.4 19.4 10.6": ["fictive"], "20.8 8.7 4.0": ["bombproof"], "7.8 7.9 7.4": ["kilojoules"], "7.5 8.2 8.8": ["pubco"], "13.8 1.7 9.0": ["rhapsody"], "4.5 4.0 10.6": ["conjunto"], "12.5 11.0 12.3": ["carny"], "7.7 5.5 17.9": ["ascot"], "2.8 1.5 10.6": ["handbells"], "10.3 8.3 43.9": ["tartare"], "2.4 -0.5 23.9": ["porcelains"], "6.3 -3.2 -6.8": ["facilites"], "11.6 2.2 6.3": ["watchin"], "-2.9 7.4 11.4": ["gages"], "2.5 9.7 13.1": ["sluices"], "-3.6 8.1 -2.9": ["encouragements"], "3.2 3.8 10.3": ["transporation"], "20.1 -4.2 12.0": ["aahed"], "21.4 11.2 6.4": ["larges"], "2.3 9.1 3.1": ["ain"], "1.2 20.3 17.5": ["spitball"], "-1.5 5.9 3.2": ["unsaturated"], "20.6 -3.5 10.6": ["ified"], "13.2 12.5 11.8": ["upholsterer"], "-2.6 15.9 -0.5": ["overflew"], "19.3 5.0 17.2": ["daub"], "2.5 13.7 4.6": ["blurriness"], "6.8 5.7 11.6": ["manny"], "4.5 7.6 42.9": ["porgies"], "0.2 13.0 7.6": ["adivasi"], "23.4 22.8 12.6": ["bringer"], "2.0 5.6 2.4": ["ef"], "5.2 -6.0 8.7": ["tamperproof"], "5.8 20.9 2.4": ["electromagnetism"], "-8.2 4.3 9.0": ["engraftment"], "14.0 4.5 1.8": ["trilled"], "11.7 12.0 9.7": ["nightlight"], "2.5 3.4 18.9": ["greengrocers"], "5.0 21.4 6.7": ["marxist"], "0.9 2.8 8.7": ["fleetwide"], "0.8 9.5 -3.0": ["effusion"], "-2.7 8.0 2.8": ["overmedicated"], "7.4 8.1 26.9": ["ambrosia"], "-3.8 1.9 -1.3": ["absorbency"], "2.4 3.8 2.6": ["reinterprets"], "2.7 4.4 8.7": ["hort"], "14.5 9.3 14.0": ["conveyer"], "-1.4 10.6 -6.8": ["patdowns"], "4.7 -2.9 18.0": ["bsd"], "10.5 7.6 24.6": ["geishas"], "9.9 2.0 13.2": ["hootenanny"], "12.9 24.9 7.3": ["wielder"], "1.3 2.7 5.7": ["phytosterols"], "-2.6 14.0 17.0": ["ums"], "6.4 12.2 22.0": ["sunnies"], "-6.1 -1.1 2.6": ["fractionated"], "7.1 20.6 5.5": ["ruffian"], "4.7 16.8 6.4": ["cleaves"], "4.3 8.3 17.6": ["pers"], "4.8 6.9 13.1": ["vampy"], "0.9 9.9 18.8": ["northcentral"], "-3.3 5.8 -1.3": ["litterateur"], "-1.8 7.0 10.4": ["moisturisers"], "11.0 2.8 1.6": ["disintermediation"], "-0.5 4.8 -0.4": ["ambassadorships"], "-5.9 5.8 10.2": ["absense"], "11.1 6.5 13.6": ["spliff"], "16.3 36.8 3.5": ["unconquerable"], "2.4 15.6 5.3": ["impels"], "-4.5 13.1 16.5": ["extirpated"], "11.6 -0.1 9.7": ["toddled"], "12.1 11.8 14.5": ["yokes"], "13.9 16.8 3.0": ["undulation"], "7.4 14.0 -3.4": ["unmasks"], "-4.2 7.0 15.2": ["wirehouses"], "16.5 -1.5 7.3": ["loungers"], "14.8 0.1 7.6": ["burped"], "5.1 16.7 4.7": ["shadier"], "-0.4 0.0 6.5": ["gigged"], "4.2 2.0 2.6": ["watermarked"], "-9.1 -0.2 3.2": ["margining"], "10.4 8.6 21.7": ["bristly"], "8.7 15.4 3.7": ["peeve"], "10.3 2.9 39.5": ["wontons"], "9.6 3.9 6.9": ["boilermaker"], "9.8 22.6 7.1": ["neocolonial"], "-8.8 15.1 7.6": ["emotionality"], "4.2 7.7 7.6": ["ists"], "6.0 3.5 11.8": ["stocktake"], "-0.3 -0.0 5.5": ["wittier"], "-1.6 18.7 3.2": ["backfields"], "-0.1 5.8 10.2": ["proppant"], "18.2 19.8 20.7": ["trebuchet"], "-12.5 15.6 -1.5": ["ibid"], "1.8 4.9 12.5": ["bindi"], "2.0 10.2 8.1": ["inorder"], "-2.1 8.6 9.7": ["urbanist"], "1.7 -1.3 12.9": ["epi"], "-5.9 -5.5 1.7": ["addenda"], "-1.6 13.1 22.1": ["halyard"], "8.7 15.3 6.2": ["gladdened"], "11.0 24.4 13.8": ["ingrate"], "7.8 11.7 9.3": ["offie"], "9.1 11.3 5.7": ["goalward"], "11.2 5.6 12.7": ["aww"], "-3.6 14.0 8.0": ["undertrained"], "2.7 2.7 2.6": ["odometers"], "-0.1 10.9 4.1": ["convergences"], "-2.3 6.7 7.9": ["castmembers"], "7.4 7.3 5.3": ["hypothesizing"], "7.4 19.8 4.7": ["nutcases"], "10.0 15.4 2.9": ["pentagram"], "1.1 7.6 4.0": ["greenkeeper"], "-3.2 3.4 6.7": ["poetical"], "13.0 11.9 9.3": ["headbangers"], "8.4 17.5 -1.6": ["indispensability"], "0.5 -0.8 -3.8": ["identifed"], "-6.1 8.8 6.9": ["jurisprudential"], "1.8 -3.7 3.1": ["pcp"], "-2.7 6.7 16.0": ["talaga"], "-5.1 -5.9 5.3": ["chargeoffs"], "4.7 6.7 13.5": ["scaler"], "10.6 21.3 16.5": ["parabola"], "-0.3 8.6 8.9": ["favs"], "2.6 8.1 25.8": ["thali"], "3.9 -0.8 0.1": ["straightway"], "9.2 0.2 4.8": ["driers"], "-2.4 5.2 8.4": ["catalogers"], "12.0 10.5 7.3": ["lyre"], "7.7 10.7 16.5": ["bramble"], "10.5 2.4 4.9": ["cel"], "-2.7 2.8 5.7": ["phenylalanine"], "13.5 11.9 15.3": ["databanks"], "9.8 -2.3 -8.0": ["fomer"], "5.7 -2.5 7.6": ["crystalized"], "-2.0 4.4 14.2": ["nonmotorized"], "6.3 0.4 31.4": ["torta"], "4.2 18.5 11.7": ["seemly"], "8.2 9.3 25.6": ["ouzo"], "6.5 9.9 14.4": ["stockholdings"], "6.4 8.1 -0.5": ["benami"], "4.9 7.3 7.2": ["classing"], "0.5 2.3 6.6": ["housewarming"], "-7.2 8.9 14.0": ["hydrolyzate"], "16.4 18.5 20.5": ["boogers"], "0.9 13.2 9.6": ["lodestar"], "1.5 -0.6 4.1": ["nightgowns"], "0.6 6.3 2.9": ["undersupplied"], "6.0 22.7 12.7": ["babyfaces"], "19.6 14.7 19.4": ["terra"], "7.4 9.6 6.2": ["anemometer"], "8.6 3.0 18.6": ["uke"], "7.9 1.3 16.5": ["fluffier"], "-0.2 3.0 -0.1": ["premed"], "-3.1 1.8 11.0": ["fourplex"], "-4.0 7.8 1.3": ["plenipotentiary"], "16.1 26.9 6.7": ["nazis"], "10.4 15.1 18.9": ["nunchucks"], "-0.4 9.2 4.3": ["occluded"], "18.0 18.2 2.8": ["ingrates"], "6.0 -3.4 -3.1": ["iss"], "43.9 12.5 17.5": ["goliaths"], "1.1 -9.4 13.4": ["lipo"], "1.4 9.6 1.2": ["percenters"], "9.7 3.0 10.9": ["ike"], "6.3 5.5 16.0": ["colloidal"], "5.0 3.5 47.8": ["pilchards"], "9.4 -0.1 4.7": ["recordholder"], "-0.1 13.6 5.7": ["watchfulness"], "-2.2 4.4 5.9": ["mcfe"], "0.2 22.2 11.2": ["prepositioned"], "4.0 14.9 2.9": ["assimilates"], "6.5 7.4 43.6": ["terrapins"], "5.4 0.9 14.6": ["buntings"], "5.9 10.4 26.5": ["lochs"], "2.8 5.7 43.0": ["seafoods"], "2.9 17.6 9.9": ["netas"], "-4.9 9.9 9.9": ["neuters"], "4.2 5.9 9.4": ["truncation"], "10.0 6.3 1.4": ["whisperings"], "0.6 30.8 1.2": ["persecutor"], "15.2 3.9 17.9": ["gimp"], "2.3 10.6 5.6": ["funner"], "5.2 0.0 6.3": ["uninformative"], "6.3 10.2 -1.3": ["andother"], "8.3 18.3 -0.2": ["troublespots"], "8.4 10.4 10.7": ["musclemen"], "0.4 10.8 3.6": ["unretire"], "-1.4 5.7 8.2": ["pronouncer"], "-4.2 0.4 4.2": ["lubiprostone"], "3.0 2.0 17.8": ["pipette"], "0.6 7.0 3.0": ["uplinked"], "-2.8 17.6 2.7": ["vicinities"], "-2.7 3.0 20.0": ["bodyboarding"], "4.4 13.7 14.3": ["gunna"], "7.9 9.1 7.9": ["greediness"], "0.8 7.9 9.9": ["officiant"], "1.3 3.2 17.0": ["ruching"], "4.7 22.0 -3.2": ["radiations"], "6.1 1.8 15.1": ["bakeware"], "0.6 4.3 29.7": ["cygnets"], "0.4 8.8 8.8": ["quickies", "ghettoized"], "-6.6 16.1 13.8": ["cinephile"], "5.5 5.8 16.6": ["abundances"], "-2.1 4.6 0.4": ["hypothesised"], "3.3 21.5 11.2": ["regather"], "-4.1 5.0 4.5": ["dramaturgy"], "2.0 4.1 15.4": ["earwax"], "18.7 7.9 18.0": ["tossers"], "3.9 3.3 0.8": ["majorette"], "-5.3 12.6 2.1": ["attentional"], "11.3 4.4 14.1": ["metrosexuals"], "-0.4 13.6 0.5": ["unbridgeable"], "-4.9 8.1 5.0": ["recirculate"], "-5.1 4.1 18.4": ["kaumatua"], "0.8 4.6 3.9": ["outsole"], "1.8 4.0 8.4": ["holla"], "1.4 11.0 20.9": ["poling"], "3.9 3.4 2.9": ["happenin"], "4.1 25.9 8.3": ["hotkey"], "3.1 13.1 4.5": ["abrasiveness"], "6.4 13.0 8.7": ["reverentially"], "7.9 0.9 1.8": ["vitaminwater"], "10.4 2.9 2.9": ["overinvestment"], "-10.9 2.7 2.5": ["amendable"], "17.0 2.2 13.1": ["slickers"], "-0.6 -0.4 14.0": ["storewide"], "1.4 12.8 10.9": ["hydrographic"], "2.0 11.7 6.0": ["acidly"], "-7.0 8.1 2.5": ["ratably"], "-2.4 2.7 11.0": ["ngayon"], "-4.1 12.1 4.1": ["catechins"], "-2.9 19.1 10.1": ["pointspread"], "13.1 7.7 13.5": ["codgers"], "7.6 18.5 12.6": ["heartlessness"], "3.2 21.9 9.8": ["counterfactual"], "20.0 6.7 41.5": ["barnacle"], "-2.6 8.7 12.6": ["annuitants"], "-3.6 1.8 6.4": ["shortterm"], "4.0 11.9 16.2": ["algo"], "1.6 7.8 10.0": ["anticline"], "2.0 25.3 6.4": ["footsoldiers"], "-2.4 4.6 0.9": ["taskforces"], "1.0 19.6 12.2": ["psalmist"], "6.4 17.5 6.0": ["egotist"], "0.5 18.6 18.6": ["kimura"], "6.4 -4.8 2.9": ["vibrance"], "-6.1 9.8 6.4": ["overrate"], "12.1 15.2 6.9": ["despoiled"], "22.2 10.2 13.7": ["firehose"], "-3.4 -1.5 -7.2": ["atsec"], "6.4 3.3 4.8": ["kickabout"], "10.9 5.5 14.5": ["vegetal"], "-0.7 18.6 15.9": ["headbutts"], "11.7 7.3 15.8": ["wildebeests"], "1.4 11.6 9.5": ["lovastatin"], "6.9 6.3 21.1": ["tuque"], "1.8 1.8 5.8": ["pharmacogenetics"], "11.8 4.8 12.4": ["pon"], "-4.9 14.0 6.9": ["oxidant"], "9.8 13.7 -0.8": ["ize"], "6.5 10.3 14.0": ["rosewater"], "-3.7 -2.4 5.1": ["lanolin"], "-4.8 0.1 0.5": ["abacavir"], "-4.5 2.5 7.5": ["microfracture"], "0.1 11.5 20.4": ["cornermen"], "2.9 12.8 4.2": ["vituperation"], "3.7 18.7 12.9": ["pusillanimous"], "-0.2 3.3 4.3": ["hadnt"], "2.4 0.9 9.6": ["herbarium"], "3.1 -2.3 14.0": ["pleating"], "-2.8 19.9 9.0": ["shalom"], "2.8 12.4 12.1": ["bodycheck"], "2.9 0.4 12.8": ["haikus"], "-0.5 -0.2 8.4": ["ligation"], "-2.1 12.7 19.4": ["arrack"], "3.8 -0.6 4.3": ["noncurrent"], "2.2 5.8 -3.2": ["professionalise"], "17.6 6.4 -4.0": ["aquisition"], "-4.3 9.1 9.3": ["lightheartedness"], "18.7 5.1 5.0": ["grandaddy"], "0.4 3.8 12.0": ["cysteine"], "10.5 11.0 18.0": ["layabout"], "2.2 10.0 7.1": ["convo"], "10.8 3.9 3.0": ["cloisters"], "7.9 16.9 5.8": ["shanking"], "7.5 19.1 10.6": ["downdrafts"], "0.9 2.6 8.1": ["insulins"], "13.1 -6.0 12.5": ["diamante"], "15.4 29.4 6.0": ["teleporting"], "16.0 7.4 32.1": ["chook"], "17.1 13.1 3.9": ["hunching"], "1.9 0.9 5.0": ["metabolically"], "14.0 13.0 2.3": ["iconographic"], "-8.9 6.6 0.6": ["divisionals"], "-14.9 8.1 8.6": ["reallocations"], "2.8 13.1 0.8": ["decrypting"], "0.5 7.8 4.2": ["unfriend"], "17.0 13.1 12.2": ["disgorging"], "12.9 8.8 15.8": ["messily"], "0.2 -2.1 1.8": ["payslips"], "12.4 9.9 23.7": ["furred"], "-6.7 1.3 10.3": ["glutamine"], "10.3 9.0 37.3": ["cetacean"], "3.7 14.2 34.4": ["harvestable"], "14.9 15.9 12.7": ["doppelgangers"], "6.6 0.8 14.7": ["corseted"], "-4.4 10.7 2.9": ["azadi"], "1.5 4.7 11.0": ["omerta"], "-2.0 7.2 5.3": ["pontifical"], "11.9 7.2 3.6": ["elongating"], "3.5 11.3 4.0": ["manoeuvrings"], "6.2 4.9 43.1": ["alewife"], "20.1 11.2 9.5": ["buccaneering"], "6.2 7.0 25.1": ["grayling"], "1.8 13.0 3.1": ["ungenerous"], "4.2 4.5 6.9": ["songbooks"], "-0.2 8.2 13.0": ["cattiness"], "2.2 3.3 0.9": ["injunctive"], "12.3 1.7 5.7": ["ology"], "-6.8 5.0 11.5": ["nonstops"], "-10.4 4.6 3.4": ["colorists"], "-5.8 9.6 5.7": ["isomer"], "11.5 20.0 11.4": ["oligarchies"], "8.9 2.2 23.8": ["crema"], "15.6 22.5 5.7": ["cowers"], "-4.9 -2.4 5.4": ["folios"], "3.5 16.4 16.7": ["nativism"], "4.5 2.4 14.3": ["djembe"], "8.9 -2.4 5.6": ["lightings"], "7.6 0.2 -2.9": ["llc"], "17.0 7.7 8.6": ["slinked"], "0.8 8.8 7.2": ["songsmith"], "5.4 6.4 10.1": ["punkish"], "8.3 9.0 47.0": ["triggerfish"], "2.1 10.7 3.8": ["coalescence", "gangbanging"], "9.1 5.2 0.8": ["nitroglycerine"], "7.1 13.3 20.8": ["hydrofoil"], "-2.6 5.0 6.5": ["footway"], "13.1 9.6 4.5": ["hirer"], "0.8 1.6 12.5": ["garba"], "12.7 0.2 8.0": ["newpaper"], "-0.7 11.3 1.3": ["therewith"], "15.1 12.5 3.0": ["molehills"], "1.4 -0.1 2.1": ["unclogged"], "8.0 11.1 9.1": ["agin"], "-5.3 13.9 2.1": ["settlor"], "3.8 5.8 5.6": ["greenshoe"], "12.7 18.6 15.3": ["snarly"], "3.5 3.8 14.4": ["euthanised"], "-4.5 22.2 8.7": ["submunitions"], "16.0 1.6 8.2": ["puede"], "-5.0 15.5 -2.7": ["resultantly"], "7.1 1.0 13.4": ["nyc"], "-9.2 8.7 24.9": ["shoreland"], "0.9 4.5 -7.1": ["evolvement"], "0.1 0.9 4.2": ["rakhis"], "-7.9 7.4 4.0": ["codicil"], "3.5 5.8 10.6": ["calligraphers"], "8.1 -5.2 3.5": ["balers"], "1.4 1.5 7.5": ["gamewinner"], "3.1 22.3 29.9": ["phragmites"], "-6.3 -0.0 8.5": ["trichomoniasis"], "-9.8 8.0 1.1": ["insightfully"], "7.9 10.2 8.5": ["lmao"], "3.3 10.8 4.1": ["disowns"], "3.8 18.6 12.8": ["somone"], "8.2 1.8 9.0": ["hotmail"], "0.9 6.0 3.1": ["ung"], "4.3 2.0 11.7": ["sixths"], "-3.5 10.1 4.9": ["pralatrexate"], "5.9 7.2 -0.3": ["hopscotching"], "15.1 13.7 3.2": ["vaporous"], "10.7 2.8 -13.3": ["sro"], "7.6 17.8 3.5": ["unwelcomed"], "-1.6 3.1 14.1": ["lw"], "2.5 4.4 5.4": ["neg"], "16.3 16.3 24.5": ["piratical"], "-4.2 7.9 -1.1": ["ticagrelor"], "9.4 5.2 5.0": ["atm"], "1.5 9.3 -2.2": ["vaporization"], "14.9 13.2 14.9": ["wriggles"], "6.0 7.8 21.9": ["buttercup"], "13.4 7.1 -0.8": ["overstatements"], "3.7 -4.2 0.5": ["additonal"], "5.9 11.3 1.6": ["perceivable"], "-6.7 10.9 3.5": ["unfitness"], "-5.2 -1.4 15.6": ["masterbatch"], "14.6 6.6 5.7": ["aftertax"], "-3.0 7.7 7.1": ["regresses"], "5.1 16.5 2.3": ["photoelectric"], "10.5 14.2 14.7": ["freeloader"], "10.7 8.6 0.4": ["mesmerizes"], "6.9 7.1 -2.3": ["remeasurement"], "-5.4 16.8 0.0": ["interethnic"], "-3.2 4.1 1.9": ["uninvestigated"], "-0.6 14.8 -2.1": ["misconstruing"], "0.2 27.3 -0.9": ["splittist"], "0.5 6.2 1.5": ["practioners"], "7.8 3.1 10.5": ["decanters"], "-7.2 -5.8 -0.6": ["sessional"], "-7.8 21.2 4.8": ["backburning"], "11.7 12.6 12.0": ["bonking"], "10.1 13.5 5.3": ["boor"], "19.3 1.1 17.1": ["bronco"], "1.5 1.9 12.1": ["oligodendrocytes"], "6.0 13.0 12.4": ["lexical"], "5.3 6.8 5.0": ["whited"], "12.2 18.1 12.8": ["monocultures"], "1.7 12.8 17.2": ["directionality"], "2.1 6.7 41.0": ["overharvesting"], "11.6 8.7 13.7": ["nonscientific"], "10.5 16.6 3.2": ["rend"], "12.5 5.1 24.2": ["palmetto"], "-8.2 9.5 -0.2": ["rebbe"], "2.6 3.8 12.1": ["underspending"], "1.8 3.5 5.8": ["hardgoods"], "4.1 4.1 4.2": ["auspiciously"], "9.1 8.1 12.4": ["yous"], "4.0 7.4 0.4": ["initialized"], "7.4 4.0 48.9": ["dory"], "12.0 12.2 1.8": ["pyromaniac"], "8.0 9.7 13.4": ["granule"], "10.9 0.9 7.9": ["sequencers"], "4.2 7.2 7.1": ["feting"], "-4.2 4.9 1.9": ["desulfurization"], "5.4 8.7 18.9": ["moister"], "8.1 9.2 17.8": ["sallow"], "14.6 3.0 18.0": ["chintz"], "8.6 -2.9 9.6": ["wananga"], "3.6 6.6 8.2": ["filenames"], "-3.9 8.5 6.4": ["kts"], "4.2 1.0 12.9": ["panniers"], "1.5 0.7 -2.3": ["splitsville"], "0.5 12.0 10.7": ["unrepeatable"], "5.3 4.8 14.1": ["glandular"], "2.8 7.2 19.0": ["chert"], "3.4 0.1 7.6": ["geoscientist"], "18.4 18.3 7.0": ["superheros"], "7.5 13.3 7.9": ["zoloft"], "3.1 13.6 4.4": ["flippancy"], "-1.0 6.9 2.1": ["decongestion"], "12.3 19.6 16.2": ["guiltless"], "-5.3 12.1 9.1": ["headmen"], "10.0 13.8 22.2": ["clapper"], "-0.1 15.5 7.7": ["paragliders"], "4.6 8.2 27.7": ["jakes"], "-6.2 -6.5 4.9": ["menarche"], "-0.4 6.9 6.7": ["chawl"], "7.8 1.4 9.5": ["futons"], "14.4 12.8 9.6": ["scree"], "1.0 16.0 7.9": ["untargeted"], "-12.0 -2.5 -0.8": ["hydroxyurea"], "8.3 2.0 12.4": ["miscanthus"], "10.1 8.6 20.3": ["dowels"], "10.4 6.8 15.2": ["playscape"], "18.6 5.5 2.3": ["trundles"], "7.5 7.0 5.3": ["imho"], "3.0 2.3 13.6": ["kombucha"], "-2.7 5.8 15.1": ["congresswomen"], "12.0 12.4 11.2": ["animists"], "26.5 -3.0 2.0": ["telecomms"], "5.1 6.9 35.3": ["kumquats"], "-2.3 -3.9 2.5": ["videocast"], "-1.1 16.8 4.3": ["polarizes"], "3.5 6.0 2.6": ["iz"], "13.4 -0.3 3.7": ["reorg"], "-0.8 10.9 15.0": ["missal"], "7.0 21.8 11.0": ["mapmakers"], "1.2 -3.1 5.3": ["hwy"], "-8.8 10.8 8.0": ["dermatologic"], "18.2 4.7 7.6": ["wheezy"], "-2.6 10.5 25.8": ["tropicals"], "0.4 -0.6 -8.8": ["restyling"], "14.6 9.3 24.3": ["puffers"], "1.7 13.5 4.9": ["nicht"], "-7.1 -1.3 6.6": ["timetabled"], "4.0 7.0 2.4": ["gravimetric"], "2.4 6.8 27.1": ["paddleboard"], "1.9 4.5 14.3": ["crustal"], "24.8 5.3 18.3": ["plasticine"], "11.1 23.8 -0.9": ["virulently"], "17.6 17.3 11.1": ["putz"], "1.5 8.3 4.3": ["homeside"], "13.2 2.4 32.0": ["cress"], "12.5 8.0 15.5": ["reaming"], "2.6 5.5 5.2": ["rms"], "13.8 6.2 6.8": ["pinballed"], "9.9 10.4 17.3": ["roundworm"], "3.5 1.9 21.5": ["glasswork"], "8.1 4.5 3.9": ["fixturing"], "13.6 18.5 8.3": ["machination"], "2.7 8.8 -5.6": ["ruggedly"], "18.4 6.2 8.5": ["lept"], "-1.8 -2.4 3.8": ["remortgaged"], "2.3 4.9 1.5": ["edgiest"], "-4.4 13.3 -1.9": ["unprivileged"], "-3.2 2.2 14.5": ["val"], "-7.9 2.3 4.8": ["immunosuppressants"], "6.3 7.4 30.8": ["pawpaw"], "14.5 16.9 13.3": ["spaz"], "17.8 2.7 16.6": ["supersizing"], "4.3 -4.4 15.5": ["craftwork"], "-2.4 -1.2 -1.9": ["compliances"], "8.9 12.1 2.1": ["microparticles"], "9.6 6.3 27.8": ["taters"], "2.5 5.8 28.8": ["tabbouleh"], "10.3 15.3 5.0": ["compadre"], "19.2 12.9 15.9": ["crunchers"], "-1.4 0.6 3.0": ["novela"], "17.5 2.6 -1.1": ["ninefold"], "13.3 3.9 8.8": ["shonky"], "3.0 10.5 14.1": ["undernourishment"], "20.0 2.5 11.9": ["hefting"], "14.4 10.3 3.0": ["thermoses"], "-0.7 10.0 0.7": ["hiplife"], "13.5 13.8 6.4": ["characterless"], "-7.2 4.0 9.2": ["transfection"], "3.0 11.4 10.6": ["unscented"], "7.6 10.5 26.4": ["custards"], "10.8 10.4 13.7": ["dustpan"], "-5.6 8.3 7.7": ["quantitation"], "-1.5 0.8 3.0": ["internetworking"], "6.0 0.7 9.9": ["rubdown"], "-6.8 6.8 2.9": ["infomation", "injurys"], "2.4 13.9 6.6": ["plebeian"], "1.1 3.0 5.3": ["longhaul"], "5.3 14.3 2.6": ["chevrons"], "13.2 9.0 7.8": ["scribbler"], "3.5 1.8 17.8": ["perlite"], "2.5 7.2 9.6": ["dancey"], "3.0 5.3 12.5": ["propranolol"], "-3.2 -2.0 13.4": ["premenopausal"], "11.8 10.5 10.8": ["nauseatingly"], "-3.6 2.7 21.3": ["ama"], "10.4 6.1 3.9": ["dozes"], "3.8 4.0 11.4": ["italy"], "9.4 13.7 2.3": ["ereader"], "4.7 6.3 -5.5": ["zum"], "10.1 30.4 4.0": ["squaddies"], "9.2 13.5 17.2": ["winching"], "-0.7 10.2 6.2": ["outpitch"], "-4.3 2.1 9.3": ["topscorer", "utrophin"], "5.8 7.2 22.0": ["chinstrap"], "-9.5 14.3 3.8": ["isoniazid"], "7.8 8.7 12.9": ["nucleation"], "6.0 12.3 11.8": ["penitents"], "4.8 8.1 5.5": ["disinvestments"], "18.8 7.2 15.8": ["rejigger"], "14.7 11.6 10.1": ["genies"], "6.4 9.8 4.6": ["befalling"], "18.4 9.0 7.4": ["shysters"], "2.9 5.5 3.4": ["keystones"], "-7.1 12.9 4.3": ["pluralities"], "2.4 9.1 6.9": ["bracketology"], "17.4 19.1 -0.6": ["deathtrap"], "1.7 15.9 7.5": ["begotten"], "11.2 13.2 2.7": ["prophesying"], "16.9 -0.3 12.6": ["columned"], "5.7 4.1 0.0": ["monetised"], "11.2 4.4 -1.6": ["atriums"], "-0.7 5.8 37.7": ["breadfruit"], "5.2 5.8 2.2": ["unremarked"], "11.3 12.8 13.3": ["twerp"], "-0.3 -1.2 6.8": ["gynecomastia"], "2.6 -0.1 -0.1": ["nonbusiness"], "5.2 1.1 1.9": ["modernizations"], "6.4 9.7 7.3": ["reassesses"], "10.0 6.8 19.4": ["hosepipe"], "3.4 9.4 5.4": ["newsfeeds", "probusiness"], "0.8 3.5 -2.9": ["remanufacture"], "10.0 9.9 10.5": ["egomaniacs"], "6.4 6.6 13.4": ["gui"], "3.3 6.9 8.4": ["summiteers"], "-2.7 10.4 11.1": ["ductile"], "11.6 7.2 7.0": ["plumps"], "0.2 3.8 53.6": ["crabber"], "2.2 3.7 5.5": ["oversleeping"], "1.8 3.4 8.5": ["sociocultural"], "-10.1 4.4 7.6": ["poppier"], "-8.2 2.0 13.9": ["urethral"], "-0.1 -1.1 7.7": ["wangle"], "9.5 7.6 12.6": ["fifa"], "11.2 12.5 18.0": ["teardrops"], "15.1 6.0 -2.1": ["pneumatics"], "-2.6 -0.8 -0.2": ["listservs"], "13.5 15.7 9.8": ["surreally"], "-1.4 9.8 6.5": ["overdramatic"], "-1.1 4.5 0.8": ["rewritable"], "-6.5 -2.6 14.5": ["noneconomic"], "14.3 12.3 15.1": ["dragline"], "1.6 7.0 10.4": ["tracksters"], "-5.4 14.1 -0.3": ["otolaryngologist"], "6.3 17.0 1.5": ["forbearers"], "10.0 11.4 27.7": ["begonia"], "2.5 11.4 11.7": ["theyll"], "-1.7 4.2 1.1": ["forewoman"], "18.5 15.9 17.9": ["tapeworms"], "11.5 16.4 1.3": ["ingratiate"], "-0.6 5.3 3.9": ["pravastatin"], "-6.6 1.5 3.6": ["collateralization"], "6.9 6.4 11.5": ["junker"], "18.2 1.9 18.5": ["curlicues"], "-2.5 6.4 4.2": ["judiciaries"], "11.8 -2.4 8.9": ["htm"], "2.7 -2.2 2.3": ["buttonholed"], "-1.4 11.9 1.8": ["unaccomplished"], "5.4 31.3 11.4": ["thumbstick"], "7.7 9.7 4.6": ["immolation"], "5.8 13.9 4.8": ["snorers"], "-1.9 6.3 20.2": ["cordials"], "2.4 29.8 15.2": ["narcos"], "3.7 -7.6 -0.3": ["adjudicates"], "5.8 21.2 -3.9": ["advantageously"], "1.4 8.6 17.6": ["cowpea"], "-4.5 1.8 10.9": ["grenache"], "2.6 8.7 4.4": ["kilobyte"], "9.5 21.9 24.3": ["biters"], "4.8 -1.5 -6.4": ["laywer"], "4.2 0.5 5.5": ["lecithin"], "13.0 14.3 22.0": ["pikes"], "-5.0 6.6 11.2": ["moisturized"], "4.1 17.0 5.8": ["itched"], "8.1 5.7 1.8": ["responsively"], "-5.2 5.5 19.1": ["outmigration"], "4.8 -1.5 10.9": ["allen"], "-0.7 5.0 12.0": ["oenophiles"], "9.9 -4.9 4.0": ["yoo"], "1.7 6.0 7.4": ["obscurities"], "1.3 15.9 30.0": ["seamounts"], "0.3 13.6 19.7": ["westerlies"], "0.7 1.9 5.0": ["practicals"], "9.7 7.5 9.8": ["lambda"], "14.1 -2.7 5.0": ["moseyed"], "0.7 0.8 45.3": ["tilefish"], "16.0 0.8 5.8": ["hocking"], "7.7 2.7 12.9": ["oversaturation"], "6.3 10.1 13.3": ["repopulated"], "1.0 4.9 29.6": ["porterhouse"], "-6.2 12.5 1.0": ["associational"], "9.6 10.0 23.0": ["larch"], "10.1 2.5 2.5": ["keyring"], "11.1 2.1 12.4": ["scratcher"], "4.4 10.4 6.0": ["adeptness"], "-1.2 6.6 26.0": ["unsalted"], "1.6 5.2 1.9": ["preoccupies"], "3.9 7.5 7.4": ["genially"], "8.0 19.0 9.1": ["afterburner"], "6.9 0.8 3.7": ["sublicensing"], "17.2 12.8 19.8": ["artic"], "9.7 2.3 29.9": ["pied"], "-3.3 1.3 10.5": ["backloaded"], "-4.9 8.2 5.6": ["beamforming"], "4.1 7.6 -1.5": ["desegregating"], "-4.9 7.7 6.5": ["undernutrition"], "6.7 12.6 33.1": ["trotlines"], "3.5 13.4 2.9": ["pathfinders"], "-4.7 7.9 4.1": ["subdistricts", "chassidic"], "8.7 2.6 14.4": ["miami"], "4.0 16.6 17.2": ["rusts"], "-10.2 5.7 6.3": ["riboflavin"], "8.3 3.7 7.0": ["babbled"], "-2.4 3.5 6.4": ["wilayat"], "-4.3 3.6 10.3": ["restriping"], "-5.2 12.4 2.2": ["oritavancin"], "2.3 13.4 6.4": ["caucusgoers"], "1.7 11.2 15.7": ["chocoholic"], "0.3 3.6 8.7": ["downshifted"], "-2.0 12.3 3.8": ["abu"], "30.9 15.6 15.9": ["pixies"], "2.4 33.4 12.3": ["mages"], "6.2 14.6 14.2": ["ultraviolent"], "-8.8 8.1 9.1": ["catechists"], "6.6 4.8 13.3": ["greasepaint"], "3.9 13.4 12.0": ["riffage"], "16.8 12.4 14.0": ["freckle"], "1.3 -0.0 5.9": ["radiantly"], "27.1 11.1 11.8": ["lifesize"], "8.0 6.6 15.3": ["brad"], "1.4 18.7 4.0": ["desensitizing"], "2.9 1.5 1.3": ["commodious"], "2.2 7.9 45.1": ["creel"], "-4.9 5.0 7.9": ["clofarabine"], "-1.7 14.3 17.8": ["necrotic"], "2.1 17.0 15.4": ["gamekeepers"], "0.2 2.3 13.5": ["bumiputra"], "10.1 9.0 23.4": ["shucks"], "3.0 22.8 14.6": ["counterprogramming"], "6.8 -4.2 1.7": ["cp"], "-1.0 21.2 4.2": ["deminers"], "18.8 7.3 16.9": ["wombats"], "2.3 3.8 4.9": ["reinserting"], "4.6 8.9 9.7": ["urls"], "4.0 5.9 26.4": ["rutabagas"], "-3.5 -0.5 3.2": ["thiamine"], "0.2 6.5 8.0": ["atherosclerotic"], "13.6 18.7 16.0": ["pantomimed"], "-9.5 8.4 -1.7": ["pramipexole"], "0.3 1.8 1.3": ["regrading"], "4.4 16.1 10.1": ["eeriness"], "4.8 10.4 5.5": ["hyperinflationary"], "-0.6 9.7 0.7": ["phenols"], "-1.1 11.8 1.9": ["unclassifiable"], "-1.4 11.2 -9.7": ["attune"], "14.1 6.2 9.3": ["hoofers"], "11.1 -0.7 4.7": ["polishers"], "7.8 14.8 20.4": ["elephantiasis"], "1.8 8.2 13.2": ["fors"], "-1.3 7.7 16.1": ["histone"], "3.1 4.7 3.3": ["dissimilarities"], "1.0 23.8 3.1": ["overflying"], "-1.0 6.2 3.4": ["orations"], "-2.1 -2.6 9.5": ["dystrophin"], "13.0 12.4 23.9": ["breadstick"], "12.2 13.6 7.3": ["nosedives"], "2.7 3.5 12.0": ["calypsonians"], "2.3 4.7 -1.2": ["canonize"], "5.2 -2.9 11.3": ["divvies"], "18.5 3.4 17.3": ["dowager"], "1.8 -5.2 6.1": ["ampoules"], "1.2 0.3 0.6": ["befor"], "8.7 -4.0 3.4": ["tuh"], "14.1 11.6 13.4": ["splendors"], "0.4 -0.6 4.4": ["rotas"], "-13.2 11.2 1.8": ["demotivated"], "3.0 7.3 3.7": ["macromolecules"], "13.0 10.9 12.0": ["bonked"], "8.2 14.2 11.6": ["clickjacking"], "0.6 5.6 9.3": ["muso"], "10.3 0.6 5.4": ["minidresses"], "3.8 4.8 48.5": ["skipjack"], "5.4 9.6 18.0": ["pugilism"], "2.0 1.3 14.7": ["shinty"], "10.0 9.7 15.8": ["columbine"], "2.2 16.2 2.3": ["brushfires"], "8.9 14.9 9.2": ["lassitude"], "-4.9 -5.3 4.6": ["convocations"], "-2.7 -2.3 -1.0": ["essentiality"], "-4.9 12.3 2.3": ["requestor"], "12.2 8.1 14.6": ["sharpener"], "2.8 24.3 6.8": ["unfree"], "9.1 3.8 9.3": ["poms"], "5.7 4.0 -3.2": ["wird"], "1.0 12.5 12.5": ["unsheltered"], "6.6 2.3 1.1": ["holography"], "9.9 15.7 4.9": ["enthrone"], "9.4 10.0 1.2": ["coerces"], "-4.8 2.6 7.3": ["trisomy"], "9.6 7.5 11.7": ["truckies"], "6.0 -0.9 8.1": ["glossier"], "-0.8 21.1 8.3": ["legalism"], "7.3 15.4 32.4": ["alga"], "0.4 7.3 21.6": ["growler"], "-2.1 15.1 1.8": ["blameworthy"], "6.4 6.2 2.9": ["successions"], "5.3 5.7 3.6": ["evangelized"], "9.6 13.2 22.8": ["baiji"], "3.3 1.4 13.1": ["mammary"], "6.5 -1.5 3.3": ["ez"], "-1.3 8.3 11.8": ["haplotypes"], "-5.6 7.5 7.3": ["coherency"], "4.3 10.8 17.6": ["dismasted"], "3.2 6.9 22.8": ["chaat"], "9.3 12.4 7.0": ["dressingroom"], "6.4 -2.8 -1.6": ["renegotiates"], "7.4 4.6 7.9": ["sangoma"], "23.0 8.2 9.6": ["foodmaker"], "-4.3 16.2 25.9": ["icebreaking"], "5.8 -3.4 5.6": ["nel", "monaco"], "12.7 15.5 22.5": ["wenches"], "-0.4 7.2 5.5": ["lodes"], "6.0 2.8 11.4": ["dickering"], "12.0 11.9 2.7": ["identifiably"], "2.0 8.6 -0.3": ["bespeak"], "8.1 8.6 8.2": ["bandwagons"], "1.8 3.7 3.9": ["insignificantly"], "6.5 0.3 27.0": ["tortoiseshell"], "4.3 11.9 2.2": ["recognisably"], "-5.5 4.5 6.4": ["hippocampal"], "8.7 -7.1 6.8": ["mio"], "-1.3 15.9 0.7": ["outhitting"], "-0.9 24.6 1.2": ["overfly"], "10.1 6.6 7.2": ["conurbations"], "2.8 6.6 1.8": ["keynoter"], "8.6 30.9 8.8": ["redoubts"], "14.5 6.1 11.3": ["twinkles"], "1.8 2.5 8.4": ["masti"], "-5.2 4.9 22.2": ["pikas"], "13.9 6.4 17.0": ["steins"], "-1.7 3.4 13.3": ["healthwise"], "7.0 6.4 14.2": ["maxis"], "3.8 12.0 8.4": ["prolly"], "-1.5 1.4 9.3": ["seaon"], "1.6 15.7 5.3": ["extralegal", "filmable"], "-3.2 9.8 4.0": ["chemokine"], "9.7 7.9 21.2": ["parasail"], "-9.2 9.2 8.8": ["childlessness"], "3.2 0.1 20.2": ["fieldstone"], "4.8 13.9 19.7": ["birdfeeders"], "-3.2 3.4 10.0": ["socioeconomics"], "-4.5 13.9 11.2": ["selectwoman"], "12.2 8.3 17.0": ["charmers"], "9.8 14.2 4.0": ["metamorphic"], "1.4 29.6 13.1": ["inferiors"], "-2.1 0.5 8.1": ["jazzier"], "14.3 4.5 1.4": ["saleswomen"], "4.1 -2.1 41.4": ["shiitake"], "12.9 5.8 7.9": ["govs"], "15.6 9.5 36.4": ["empanada"], "4.0 4.5 17.9": ["diorite"], "4.3 13.1 3.0": ["siring"], "-6.3 0.3 8.7": ["placewinners"], "13.3 15.4 8.8": ["maddened"], "15.3 19.0 16.4": ["clod"], "13.6 17.3 10.4": ["brolly"], "11.1 7.1 9.4": ["richard"], "8.0 11.2 5.2": ["cartelisation"], "-9.4 11.3 8.6": ["reraised"], "11.2 5.8 12.5": ["brickyard"], "-5.5 0.9 1.4": ["venlafaxine"], "7.6 23.8 6.3": ["disorientating"], "2.0 23.2 6.2": ["deceits"], "-2.1 18.9 12.8": ["disembarkation"], "-2.7 6.1 15.6": ["adipocytes"], "4.3 9.1 6.5": ["woud"], "-0.1 15.8 20.2": ["chiaroscuro"], "-1.3 9.3 3.6": ["upmost"], "1.4 -3.9 6.0": ["backpay"], "5.2 12.6 0.4": ["evictee"], "21.1 14.9 11.2": ["humanlike"], "7.2 12.7 7.0": ["frays"], "9.9 17.1 3.7": ["conspiratorially"], "0.2 8.1 7.5": ["dharnas"], "12.7 12.9 5.0": ["paroxysm"], "0.7 11.5 10.1": ["bibliophile"], "1.4 13.5 4.6": ["misgiving"], "12.1 10.1 6.7": ["bunkum"], "10.2 16.0 10.5": ["theives"], "3.2 2.2 17.0": ["incorporations"], "13.4 6.7 19.7": ["pachinko"], "-4.1 6.9 11.1": ["vanaspati"], "9.1 12.0 4.9": ["visionless"], "11.8 5.7 5.0": ["bundler"], "3.2 12.2 9.6": ["feistier"], "12.3 10.5 12.0": ["anesthetize"], "3.9 13.8 36.0": ["drake"], "-0.8 1.5 5.9": ["extrapolates"], "3.5 17.2 7.8": ["perquisite"], "-4.1 9.7 3.5": ["chiefdoms"], "8.2 8.7 13.9": ["shopowner"], "9.3 2.0 6.2": ["misprinted"], "4.8 14.9 14.9": ["deking"], "-7.4 11.3 35.3": ["catfishing"], "14.6 18.9 2.9": ["numberless"], "11.0 25.0 12.7": ["furies"], "11.0 5.1 9.0": ["rheumatic"], "16.1 4.1 5.2": ["continentwide"], "8.6 23.2 4.4": ["unblockable"], "17.0 7.2 21.9": ["clothespin"], "11.9 12.6 9.3": ["autocue"], "6.1 12.6 10.5": ["doper"], "12.8 -5.0 14.6": ["rama"], "4.7 11.8 29.0": ["breakwall"], "2.9 4.0 24.0": ["dogsledding"], "-2.2 15.1 12.8": ["decease"], "22.4 7.2 15.2": ["stumpy"], "8.0 -5.3 15.9": ["gowned"], "-3.4 8.3 15.6": ["mirthful"], "-3.0 14.6 4.2": ["reproaches"], "4.0 8.9 8.3": ["unsteadiness"], "3.6 17.5 6.5": ["erosive"], "4.1 7.0 26.9": ["sassafras"], "7.3 16.5 11.4": ["alchemical"], "10.3 2.8 -1.0": ["hearkening"], "5.8 13.2 2.5": ["cannibalisation"], "9.1 2.2 15.6": ["quiff"], "13.1 10.1 16.7": ["tiddlywinks"], "-5.0 9.0 6.6": ["rewatch"], "-2.0 12.6 4.8": ["antidilutive"], "-4.5 9.1 3.6": ["candidness"], "5.5 15.7 -0.4": ["outgunning"], "13.6 4.3 7.3": ["corniche"], "8.2 8.7 13.7": ["backhanders"], "14.4 6.3 7.5": ["matchbooks"], "6.1 12.3 23.0": ["javelina"], "2.8 18.0 -3.5": ["attenuating"], "4.8 6.5 6.0": ["mpeg"], "0.3 21.5 -2.0": ["ideologist"], "6.1 13.1 6.6": ["underselling"], "1.7 9.7 2.0": ["keycard"], "1.1 10.8 -2.5": ["annointed"], "7.6 16.3 8.3": ["nativists"], "11.6 21.1 14.8": ["gauntlets"], "12.0 7.5 -7.6": ["immortalise"], "4.8 6.0 6.0": ["flatbeds"], "6.4 5.3 10.3": ["tamasha"], "9.8 4.6 8.5": ["unhitched"], "0.5 0.7 16.3": ["nitrites"], "-0.8 0.3 4.7": ["caravanning"], "-3.0 5.2 1.5": ["hundreths", "flowmeter"], "-7.0 -0.3 -2.5": ["convenors"], "-0.5 10.2 11.6": ["resegregation"], "13.1 8.5 17.9": ["greyish"], "13.7 0.5 3.8": ["otc"], "4.8 14.8 3.1": ["feeler"], "-0.6 10.6 15.4": ["pinkeye"], "1.4 6.6 7.0": ["endothelin"], "6.1 1.2 6.6": ["asenapine"], "8.6 9.1 1.7": ["compactly"], "-0.8 9.8 6.4": ["phosphorylated"], "5.7 12.7 13.0": ["prizefighters"], "0.9 11.1 18.3": ["beachgoer"], "14.3 10.4 14.1": ["espn"], "21.6 7.7 36.6": ["glop"], "4.2 5.4 19.9": ["gluts", "stephen"], "-8.0 4.0 6.6": ["angiotensin"], "-1.6 -5.1 19.9": ["jeggings"], "14.1 15.5 8.9": ["despairingly"], "-1.1 4.3 2.0": ["valsartan"], "4.4 23.3 14.1": ["raghead"], "2.0 5.9 3.1": ["salves"], "12.0 27.5 12.0": ["warlocks"], "5.1 9.3 7.5": ["ides"], "5.7 24.1 0.5": ["insuperable"], "6.0 9.3 5.3": ["adverting"], "5.3 15.0 12.9": ["whippy"], "14.8 -2.0 12.8": ["mutli"], "3.5 7.7 9.6": ["postmatch"], "4.9 -1.4 -2.6": ["aslo"], "4.4 12.5 12.9": ["mistiming"], "-2.5 9.6 1.8": ["ketones"], "-1.0 -0.9 10.3": ["oxford"], "8.8 10.3 7.8": ["tranquilizing"], "11.0 6.6 11.8": ["oy"], "1.8 8.0 13.6": ["monolayer"], "-7.9 -1.3 8.5": ["mainboards"], "-8.5 8.6 1.5": ["heterodox"], "-7.5 -2.5 20.0": ["velvets"], "8.1 0.5 10.4": ["tumbledown", "veces"], "5.2 -4.4 0.2": ["ealier"], "2.0 3.8 18.4": ["bunco"], "2.8 0.1 14.1": ["macrobiotic"], "10.8 -9.2 -0.8": ["nv"], "3.3 8.7 29.2": ["fathoms"], "5.5 14.1 -6.2": ["badmouthed"], "-5.4 8.4 3.9": ["prolife"], "0.4 4.4 8.1": ["gazetting"], "6.2 6.5 8.0": ["naturists"], "2.0 6.1 9.6": ["cycleways"], "6.5 20.4 25.2": ["omnivore"], "11.1 6.6 17.6": ["larcenous"], "1.1 3.6 37.7": ["smolts"], "1.2 4.6 4.8": ["finetune"], "-15.6 5.7 1.3": ["diphenhydramine"], "-4.1 8.8 -2.9": ["instils"], "4.7 12.0 23.4": ["manzanita"], "-2.3 10.8 14.7": ["blogroll"], "10.5 5.4 11.7": ["venti"], "3.4 2.5 -4.9": ["rebroadcasting"], "3.9 1.6 11.4": ["microeconomics"], "5.0 12.6 9.3": ["raja"], "-5.5 20.6 -5.9": ["assasination"], "4.2 2.4 2.2": ["concessioning"], "5.6 10.6 6.9": ["tantric"], "11.6 12.7 1.7": ["selfsame"], "8.3 8.7 9.6": ["shamanic"], "9.0 -2.4 11.5": ["sopped"], "4.6 6.6 40.4": ["sturgeons"], "-3.1 1.9 24.6": ["dockage"], "17.3 7.4 9.2": ["christens"], "0.9 6.0 14.0": ["sipper"], "18.2 7.1 9.3": ["grandee"], "3.5 -2.3 3.2": ["availble"], "6.1 22.8 7.7": ["homewrecker"], "12.2 3.2 9.5": ["plunks"], "6.6 8.7 6.8": ["bordellos"], "-0.3 3.0 2.1": ["ferroalloys"], "-2.2 -1.1 3.2": ["musicologists"], "-0.9 14.2 5.7": ["miskicked"], "2.9 12.2 -0.8": ["noninvasively"], "-4.0 16.9 6.5": ["stammers"], "-6.4 9.0 4.2": ["perceptively"], "9.5 8.9 12.2": ["meows"], "-5.8 9.4 15.6": ["methylated"], "4.7 1.0 5.6": ["stanched"], "-2.3 -2.1 13.8": ["reinspected"], "0.7 9.1 -2.8": ["tradenames"], "-1.6 9.3 3.9": ["unacquainted"], "0.7 6.0 9.2": ["meningococcemia"], "16.1 15.0 8.6": ["monopolizes"], "-8.4 0.2 16.0": ["marketings"], "9.6 19.7 3.9": ["outmaneuvering"], "11.2 10.8 18.3": ["brushstroke"], "6.5 15.8 12.7": ["diagonals"], "5.0 21.7 3.9": ["conscripting"], "4.3 11.2 4.8": ["digicams"], "10.0 2.5 18.9": ["aviaries"], "6.5 14.4 5.6": ["emailer"], "3.1 20.7 0.1": ["ellipsis"], "-2.8 14.7 -4.4": ["bombmaking"], "-6.5 5.4 5.9": ["tamibarotene"], "1.8 5.8 10.6": ["fingerboard"], "1.7 9.1 5.6": ["initialize"], "8.1 17.7 27.4": ["woodchucks"], "16.8 4.3 2.5": ["pictograms"], "-1.4 10.9 32.2": ["basa"], "2.8 5.0 13.6": ["eruptive"], "-8.0 5.2 -1.6": ["oncological"], "-4.3 -3.2 6.2": ["preapproval"], "-11.5 -7.5 7.1": ["gradings"], "-0.2 3.2 15.4": ["brandies"], "9.3 10.8 8.9": ["flabbergasting"], "-0.6 -1.1 6.0": ["relevent"], "0.7 9.9 4.8": ["assistances"], "-0.6 15.1 13.7": ["blackheads"], "-1.8 9.3 7.7": ["cineastes"], "-2.3 6.0 5.0": ["motormen"], "7.5 11.0 35.3": ["sedge"], "11.9 18.1 7.7": ["plutocratic"], "16.4 8.4 1.8": ["superhighways"], "2.1 11.1 7.4": ["ditz"], "10.3 10.5 11.5": ["scrunching"], "-0.6 10.7 10.3": ["disciplinarians"], "-5.4 9.2 3.8": ["thruway"], "20.2 6.6 13.4": ["hieroglyphs"], "-1.4 -1.8 18.6": ["blanc"], "9.5 10.1 11.4": ["azz"], "21.6 5.4 16.2": ["bounteous"], "10.7 11.2 3.9": ["waken"], "-1.3 16.0 11.4": ["exactness"], "-1.5 7.2 8.4": ["glimepiride"], "-4.8 8.9 8.4": ["cystoscopy"], "4.8 6.2 16.6": ["malachite"], "4.4 7.3 32.3": ["beefsteak"], "12.0 3.5 0.4": ["semiotics"], "6.9 0.4 6.8": ["nc", "somerset"], "6.3 6.7 12.7": ["moraine", "nexium"], "-3.6 16.5 9.6": ["hibakusha"], "5.5 17.5 11.3": ["outrider"], "-5.6 7.2 0.8": ["bronchodilator"], "8.3 15.6 5.6": ["asymmetrically"], "7.9 2.0 12.8": ["pabulum"], "2.9 2.9 1.0": ["parc"], "5.0 15.7 12.0": ["setpiece"], "-1.7 8.6 16.8": ["outfalls"], "4.3 23.9 6.9": ["armymen"], "-1.4 10.3 -6.7": ["unredacted"], "-5.4 8.5 11.3": ["landowning"], "9.7 -1.3 21.9": ["hong"], "2.5 14.3 1.9": ["misstate"], "11.4 12.8 -0.2": ["mistreats"], "-8.1 3.6 9.8": ["chapbook"], "9.6 3.3 10.1": ["balustrades"], "2.6 5.4 2.5": ["checkin"], "6.8 12.7 22.7": ["psyllid"], "-10.2 -0.9 6.4": ["arthroplasty"], "3.8 7.6 15.1": ["ungraded"], "-4.8 9.0 10.9": ["vias"], "9.7 15.9 22.6": ["swifts"], "-5.5 -4.2 2.1": ["levonorgestrel"], "2.4 2.5 6.3": ["blogsite"], "2.2 8.4 34.3": ["livewell"], "8.0 12.0 33.3": ["finning"], "-4.2 7.1 1.5": ["bodyshell"], "-0.2 17.9 4.0": ["weaponisation"], "6.8 5.9 5.7": ["gurudwara"], "0.2 5.6 5.0": ["unlamented"], "7.6 9.5 5.6": ["beaus"], "0.8 3.3 2.5": ["jetlagged"], "-1.4 4.9 13.9": ["aap"], "10.1 24.0 15.1": ["spitballs"], "4.6 1.3 9.7": ["cashiering"], "0.3 8.3 26.7": ["gametes"], "-7.9 9.9 13.3": ["downzoning"], "11.3 10.0 3.2": ["hightail"], "0.6 9.8 11.9": ["osteomyelitis"], "-3.7 0.0 6.9": ["interruptible"], "9.8 2.6 5.5": ["ensnares"], "-2.8 -2.2 6.0": ["decanted"], "6.6 -3.8 16.6": ["ballgown"], "6.6 -0.3 19.4": ["cardstock"], "7.9 18.6 14.2": ["shibboleths"], "4.3 5.5 0.3": ["situates"], "18.0 4.8 22.0": ["masted"], "-6.8 14.0 7.3": ["pointscore"], "7.9 5.0 15.9": ["palletizing"], "8.6 5.8 8.7": ["derivations"], "2.7 -1.4 13.9": ["barrows"], "-3.6 0.6 18.1": ["unpasteurized"], "20.1 25.1 11.1": ["zombified"], "-4.9 21.6 7.5": ["theists"], "9.3 0.5 7.9": ["sw"], "4.8 9.9 0.3": ["excises"], "16.8 0.9 16.1": ["castanets"], "3.2 5.6 6.8": ["overproducing"], "4.1 3.0 4.9": ["redomestication"], "-1.0 0.9 6.3": ["powerlifter"], "12.5 4.0 11.3": ["mortarboards"], "7.6 14.4 3.9": ["uninterruptedly"], "-7.8 7.8 12.4": ["metronidazole"], "4.1 6.5 2.4": ["gensets", "specfic"], "-2.5 12.3 9.2": ["theta"], "-2.7 6.4 2.3": ["centerback"], "12.5 14.7 12.0": ["liquefying"], "-1.6 26.9 5.6": ["harasser"], "8.3 9.9 10.6": ["zygote"], "2.5 5.0 4.4": ["outsprinting"], "-1.0 17.1 10.7": ["kinsman"], "3.5 15.0 16.8": ["capriciousness"], "18.4 17.1 7.3": ["midflight"], "5.5 6.5 10.4": ["sexton"], "18.4 4.5 8.6": ["steroidal"], "15.2 2.9 11.2": ["sodding"], "11.5 0.8 7.3": ["crystallisation"], "11.8 10.2 9.7": ["flimflam"], "2.0 2.6 4.5": ["mobisodes"], "1.3 7.7 21.1": ["grenadine"], "10.0 13.0 7.8": ["taikonauts"], "7.2 -0.2 20.6": ["feldspar"], "-5.7 8.5 5.9": ["formoterol"], "11.3 8.4 13.5": ["curtsey"], "13.2 12.5 16.6": ["splotch"], "8.0 4.2 6.6": ["quaffed"], "9.7 12.9 9.1": ["firebug"], "5.2 20.2 23.2": ["bloodsport"], "11.0 15.2 9.7": ["sickos"], "-1.3 9.7 5.1": ["freeman"], "2.6 -0.2 21.1": ["paddleboat"], "-9.0 0.6 16.3": ["reapplication"], "5.8 19.9 11.9": ["gangbanger"], "19.8 17.4 4.6": ["soundless"], "8.6 13.3 13.8": ["scroungers"], "19.3 1.9 -2.2": ["countersuing"], "2.2 8.2 24.8": ["primroses"], "-6.3 7.2 11.9": ["interdictions"], "0.1 -0.6 6.3": ["tankage"], "1.0 0.3 1.2": ["prima"], "10.5 14.4 24.0": ["guidos"], "8.9 5.1 0.0": ["biophysicist"], "12.3 12.6 9.2": ["quidditch"], "10.8 6.5 9.9": ["hoofer"], "0.2 17.0 2.9": ["addressees"], "5.7 18.6 7.6": ["whomsoever"], "2.4 -2.1 5.5": ["electrophoresis"], "8.0 2.2 14.2": ["bl"], "2.0 0.9 39.3": ["tog"], "-1.0 14.5 10.5": ["procreative"], "13.4 -1.2 15.9": ["votive"], "2.2 5.5 6.5": ["semiconducting"], "11.3 9.7 8.3": ["peekaboo"], "-2.5 10.4 -0.2": ["subclasses"], "-1.9 14.2 -3.6": ["speakerphones"], "10.3 2.2 14.0": ["supped"], "18.5 10.9 13.9": ["dinging"], "0.7 4.1 4.3": ["disapointed"], "10.8 10.7 6.4": ["farted"], "11.9 -3.3 10.4": ["oct"], "8.7 4.4 -0.7": ["intiative"], "8.5 14.6 4.4": ["paintballing"], "2.3 1.2 12.3": ["stogies"], "13.2 4.7 9.3": ["waxworks"], "-2.7 1.8 9.8": ["upskilling"], "11.7 11.2 10.0": ["peice"], "3.6 7.2 14.8": ["tectonics"], "13.3 17.3 10.0": ["damndest"], "-6.0 12.4 3.9": ["deadbolts"], "14.4 9.3 4.0": ["skulked"], "11.7 3.1 10.8": ["spleens"], "2.6 4.5 7.5": ["sheepherders"], "-1.2 5.6 6.9": ["vilazodone"], "6.5 16.9 10.3": ["czarist"], "9.0 7.8 14.0": ["languor"], "8.4 13.3 10.1": ["ejector"], "0.2 23.4 1.7": ["collectivity"], "4.9 4.7 13.2": ["souq"], "5.3 0.9 17.0": ["nasa"], "9.7 12.4 2.8": ["referrer"], "-4.1 5.6 1.2": ["recommendable"], "-5.9 20.0 9.2": ["epigraph"], "5.7 13.4 14.7": ["tentpoles"], "13.0 7.0 3.6": ["genuflecting"], "2.5 6.8 5.0": ["passably"], "2.2 8.5 13.4": ["kvetch"], "-0.1 10.8 14.9": ["talus"], "8.6 12.2 30.5": ["eggy"], "8.2 12.9 10.6": ["geodetic"], "8.7 8.3 10.0": ["offsprings"], "9.0 15.7 2.4": ["fraudulence"], "2.5 8.5 5.4": ["topological"], "-14.5 5.8 1.1": ["azathioprine"], "1.7 35.1 8.0": ["appeaser"], "-4.0 11.0 14.3": ["anodes"], "18.3 12.0 45.6": ["blowfish"], "3.5 11.0 -2.9": ["remarket"], "5.8 9.3 5.0": ["videocamera"], "-5.3 -6.4 -0.5": ["debottlenecking"], "3.6 12.9 1.5": ["unauthenticated"], "3.2 10.5 7.0": ["tunesmith"], "-12.4 7.6 7.4": ["clindamycin"], "-9.3 20.9 7.7": ["shuras"], "-5.8 11.7 7.5": ["nullahs"], "-0.3 13.6 -0.4": ["neurotoxic"], "8.8 -3.7 2.5": ["pref"], "11.4 5.8 6.7": ["sleepily"], "-6.0 5.0 16.1": ["penitential"], "-2.1 13.3 13.9": ["outskated"], "2.3 14.2 7.7": ["stan"], "-5.8 -3.7 7.0": ["matrics"], "-6.4 10.6 7.2": ["worklessness"], "23.0 8.1 5.8": ["sleekest"], "-6.7 1.3 10.4": ["vanned"], "6.1 10.6 23.4": ["batten"], "-6.4 10.5 6.1": ["bilaterals"], "-2.7 10.7 8.7": ["fudges"], "18.7 11.8 1.3": ["jostles"], "2.5 5.2 3.8": ["optionality"], "11.5 8.8 8.7": ["accoutrement"], "5.6 5.2 4.2": ["melodica"], "4.1 9.9 1.9": ["beacuse"], "8.0 -0.8 4.0": ["joing"], "10.5 12.7 19.5": ["tomcat"], "-6.4 0.5 7.5": ["postward"], "5.8 9.1 11.4": ["authenticator"], "0.7 3.2 19.9": ["fascinator"], "-2.7 8.5 9.0": ["kanal"], "-11.2 4.5 7.3": ["bitrates"], "12.7 17.8 8.4": ["shafting"], "11.6 6.0 1.9": ["environ"], "3.6 4.3 18.0": ["silty"], "-7.8 2.3 7.0": ["makeready"], "22.9 8.1 23.3": ["griffin"], "3.4 14.0 24.7": ["cordwood"], "-5.8 -0.9 1.3": ["phenylephrine"], "5.7 6.2 43.2": ["filleting"], "1.7 8.5 13.7": ["turntablist"], "7.5 9.7 14.1": ["appropriator"], "6.6 9.6 9.3": ["fibbed", "footballl"], "7.4 15.0 25.8": ["leafless"], "3.4 3.0 0.2": ["shootarounds"], "15.2 7.4 5.9": ["jockstrap"], "5.2 18.9 11.5": ["teabagger"], "14.9 11.7 7.9": ["cursors"], "14.2 4.3 12.0": ["bootylicious"], "11.6 2.1 10.7": ["nother"], "-8.2 2.7 6.7": ["periodontist"], "-0.4 29.9 3.8": ["revengeful"], "3.1 4.1 12.0": ["sunrooms"], "-1.7 7.4 -2.0": ["remunerate"], "-0.4 4.8 7.8": ["subcutaneously"], "-5.3 6.1 0.6": ["remixers"], "13.6 3.6 3.1": ["drub"], "-1.6 9.5 8.0": ["needier"], "1.5 6.3 -0.3": ["modulations"], "3.3 13.5 10.0": ["antimalware"], "7.0 1.5 5.4": ["ceremonious"], "-13.1 0.7 5.3": ["glucocorticoid"], "5.3 14.4 6.8": ["congenitally"], "17.1 3.3 1.8": ["guzzles"], "17.8 7.1 5.1": ["fiascoes"], "-1.4 13.8 6.4": ["supplications"], "17.2 25.0 20.1": ["straggler"], "7.5 3.0 5.2": ["upscaled"], "-5.1 25.9 4.2": ["resister"], "0.7 7.9 18.0": ["manioc", "ejaculates"], "-2.8 1.2 4.6": ["plexes"], "-6.9 4.4 10.2": ["bibliographies"], "-12.7 4.1 9.6": ["holdbacks"], "13.4 6.0 8.3": ["bray"], "11.9 8.4 15.5": ["whoopee"], "6.1 1.1 4.5": ["ih"], "13.5 4.6 9.5": ["polisher"], "12.3 30.0 8.1": ["bloodily"], "-1.7 11.8 -2.2": ["metabolizing"], "10.0 18.2 3.3": ["wretches"], "3.7 6.1 0.3": ["cabrio"], "12.3 10.4 7.1": ["lobotomized"], "2.0 4.2 5.6": ["dismays"], "11.5 3.2 15.5": ["finials"], "-11.0 -1.1 4.0": ["podiatric"], "-6.6 9.3 5.2": ["relevantly"], "6.6 12.6 2.8": ["sniggers"], "0.3 3.8 13.7": ["gristmill"], "-6.7 4.0 4.3": ["asphalting"], "8.5 -3.0 6.6": ["nov"], "-5.1 16.3 -3.3": ["dialoguing"], "5.4 3.3 14.0": ["sheng"], "-2.9 7.7 9.3": ["myocardium"], "6.6 18.1 24.4": ["hermaphrodites"], "9.8 8.4 4.9": ["hel"], "5.0 9.6 10.3": ["ony"], "8.7 -3.5 11.0": ["welsh"], "2.5 -1.8 13.4": ["tartans"], "8.6 1.7 2.6": ["capita"], "5.2 3.8 5.1": ["groundshare"], "4.4 6.9 17.0": ["andesite"], "1.3 4.8 11.5": ["lubes"], "8.3 8.0 32.0": ["oysterman"], "13.7 14.3 9.4": ["contorts"], "9.9 16.8 10.1": ["deflector"], "-0.6 9.1 3.7": ["ahve"], "-0.5 6.9 5.6": ["unenforceability"], "-8.8 11.3 5.3": ["charism"], "3.8 1.1 34.1": ["chevre"], "-3.0 -1.2 11.5": ["viscose"], "21.5 1.5 -0.3": ["bilion"], "12.2 16.3 13.5": ["coolies"], "11.7 9.1 7.3": ["beared"], "15.9 11.5 7.8": ["boneyard"], "3.6 -1.1 10.4": ["deb"], "4.5 13.7 5.1": ["utilitarianism"], "2.0 -1.8 9.1": ["pipa"], "3.2 13.5 2.8": ["dumbing"], "14.3 9.4 2.7": ["clangs"], "3.2 15.9 5.6": ["ideavirus"], "1.3 4.3 3.1": ["crystallography"], "12.9 4.2 0.9": ["afte"], "7.7 -3.5 5.2": ["afterhours", "beaucoup"], "16.0 -3.8 5.0": ["snazzier"], "4.2 2.7 0.7": ["softener"], "5.4 -2.0 21.3": ["vin"], "8.3 19.6 9.0": ["manoeuvrable"], "5.1 0.1 15.2": ["thresh"], "1.9 19.0 9.3": ["overreacts"], "4.3 8.0 15.8": ["polysaccharide"], "9.6 7.6 15.9": ["soused"], "-0.3 6.9 3.1": ["laryngeal"], "3.4 12.4 5.8": ["videoing"], "11.2 5.7 11.5": ["postbox"], "18.6 8.1 16.9": ["wang"], "3.0 18.0 2.8": ["schismatic"], "11.7 13.1 7.6": ["recombined"], "-1.8 2.2 -1.0": ["optometric"], "14.7 10.6 16.2": ["chinned"], "1.4 12.3 -1.2": ["rankers"], "8.6 14.8 2.0": ["asphyxiate"], "8.5 16.5 4.0": ["appeases"], "14.1 10.0 9.6": ["affixes"], "2.9 9.0 12.3": ["impishly"], "-0.3 7.8 3.5": ["evicts"], "0.8 3.9 13.3": ["ceramicist"], "12.1 20.6 -0.6": ["wikileaks"], "5.0 15.8 7.0": ["boorishness"], "-3.1 3.9 7.7": ["gallerist"], "-0.6 -2.0 5.4": ["seh"], "6.9 10.8 6.0": ["zigged"], "-0.6 1.8 8.0": ["hosters"], "-12.1 -2.2 5.2": ["testbench"], "-3.5 1.7 3.9": ["dehumidification"], "11.3 10.0 1.5": ["zagged"], "-4.4 6.0 11.6": ["freights"], "-1.8 4.8 11.3": ["makeups"], "13.7 7.6 21.0": ["tetrapods"], "-3.0 12.6 3.3": ["paramilitarism"], "7.5 1.0 10.6": ["gramme"], "-12.6 3.3 11.7": ["inclusionary"], "8.9 11.1 10.9": ["interlacing"], "6.2 6.8 5.5": ["therm"], "4.3 2.6 19.1": ["unrefrigerated"], "5.5 17.5 6.7": ["distain"], "5.1 14.4 6.1": ["trenched"], "9.4 7.5 11.3": ["twirler"], "12.4 1.7 7.7": ["rubberised"], "-11.3 2.0 12.4": ["frontloaded"], "5.4 1.9 2.6": ["manchester"], "3.9 26.9 7.7": ["blasphemer"], "1.9 11.1 16.1": ["olivine"], "-0.5 5.0 6.0": ["telmisartan"], "0.6 -5.1 3.4": ["microfinancing"], "1.4 6.3 1.0": ["redox"], "6.4 9.1 18.2": ["gos"], "-1.9 -1.5 1.5": ["empathised"], "5.1 18.3 9.9": ["tattling"], "-3.6 0.6 9.0": ["cantatas", "aat"], "3.3 -0.2 6.1": ["ager"], "1.5 3.7 6.9": ["componentry"], "1.0 5.1 5.1": ["numerate"], "-0.3 -0.5 4.6": ["intersperse"], "0.7 4.8 -0.0": ["jottings"], "-5.4 5.5 15.2": ["silviculture"], "10.2 12.6 5.9": ["buttes"], "-5.6 3.3 12.4": ["tempi"], "10.1 14.3 9.2": ["sundered"], "2.0 -6.1 11.4": ["sy"], "-10.6 1.8 11.0": ["metoclopramide"], "15.6 1.2 13.5": ["bacchanalia"], "9.5 11.1 0.4": ["disinfects"], "-11.4 5.7 9.3": ["arrearages"], "-9.6 4.3 14.1": ["dui"], "2.1 14.3 12.5": ["saith"], "-8.0 12.2 7.3": ["billeting"], "14.6 10.0 -4.9": ["troubleshooters"], "1.5 4.5 6.6": ["jots"], "-3.2 20.4 -2.3": ["universalist"], "9.6 3.6 7.3": ["drainpipes"], "10.7 16.6 4.9": ["steerable"], "4.7 4.3 17.8": ["pete"], "2.0 18.5 8.0": ["inflammations"], "8.2 7.8 1.2": ["corporatised"], "-1.5 1.4 12.0": ["ano"], "2.0 11.0 3.5": ["watchlists"], "0.7 14.9 24.3": ["netter"], "-3.6 3.2 7.1": ["interleaved"], "7.4 0.4 15.3": ["brewhouse"], "-8.9 3.1 0.0": ["discussants"], "-6.7 9.0 10.3": ["anticrime"], "6.4 14.9 9.7": ["bellyache"], "4.9 5.9 -4.8": ["mischaracterizes"], "14.5 7.2 19.3": ["pterosaur"], "8.9 15.2 21.2": ["crag"], "8.3 0.8 7.7": ["crewcut"], "3.4 6.0 10.6": ["streetwalkers"], "-2.4 5.6 7.7": ["reworkings"], "1.6 2.0 14.0": ["vel"], "2.2 15.5 6.8": ["bolthole"], "-0.7 1.5 2.0": ["copolymer"], "2.4 11.2 33.3": ["boatyards"], "-6.8 3.9 4.5": ["microvascular"], "-5.5 23.6 10.5": ["presuppositions"], "4.2 9.1 3.2": ["competitve"], "9.6 -4.0 5.3": ["feb"], "4.1 5.6 2.0": ["expecially"], "7.6 16.9 8.9": ["deviousness"], "3.1 8.0 11.4": ["retied"], "2.6 6.5 6.7": ["avi"], "8.2 16.0 11.5": ["yankees"], "11.0 3.8 4.1": ["bashings"], "12.0 24.2 3.4": ["rioter"], "-7.4 19.6 6.3": ["missional"], "3.4 18.1 -6.9": ["desisted"], "14.6 2.4 8.0": ["fug"], "-4.1 11.1 6.6": ["characterisations"], "4.3 5.7 -2.3": ["lathering"], "0.7 -0.8 -13.3": ["involvment"], "1.6 3.3 13.4": ["kris"], "-5.6 11.4 2.4": ["milnacipran"], "7.0 7.1 10.6": ["hoorah"], "14.0 -8.3 19.9": ["pkg"], "13.5 9.8 20.5": ["papery"], "7.5 21.0 13.1": ["pitying"], "2.9 0.4 20.4": ["brindle"], "6.2 0.9 12.8": ["leatherette"], "-1.8 14.6 6.2": ["magisterium"], "0.1 8.4 10.7": ["infilling"], "13.1 -0.3 8.6": ["oa"], "-3.4 13.8 5.6": ["uncharismatic"], "0.8 12.2 38.2": ["bullheads"], "7.8 7.9 10.1": ["sylvan"], "3.6 11.8 0.2": ["interlink"], "-5.4 7.7 7.5": ["keratinocytes"], "1.5 1.2 2.5": ["bootstrapped"], "10.8 17.7 7.9": ["freethinkers"], "-2.0 13.5 4.8": ["unbiblical"], "9.1 -5.3 1.0": ["theatricals"], "-1.3 5.8 12.8": ["cohabitating"], "6.3 2.5 4.0": ["reticulation"], "-12.2 10.2 3.7": ["preventions"], "2.8 1.1 6.0": ["yarmulkes"], "-4.9 6.9 4.8": ["weightroom"], "-2.9 9.6 1.3": ["incisively"], "-5.6 10.6 6.5": ["timestamps"], "19.0 11.6 14.7": ["tippy"], "17.5 20.5 13.8": ["superphone"], "4.8 -2.8 5.8": ["tuckered"], "3.0 6.8 8.8": ["freewheel"], "-1.5 10.3 5.9": ["staleness"], "3.8 10.8 8.1": ["plantar"], "-7.1 1.9 -3.8": ["covenanted"], "13.6 6.6 23.1": ["flattop"], "4.9 12.7 -1.6": ["recants"], "3.4 4.3 -1.9": ["successfull"], "0.0 1.9 2.8": ["timecards"], "-3.5 6.6 6.2": ["prejudgment"], "9.1 6.3 6.5": ["alledgedly"], "-0.9 4.2 11.6": ["goatees"], "5.9 3.4 5.5": ["swaddling"], "-0.9 -1.1 5.3": ["exonerees"], "4.6 0.8 6.6": ["pipefitters"], "12.5 16.5 21.5": ["cheeseheads"], "2.7 3.6 13.4": ["larry"], "2.0 1.2 9.0": ["nonperishable"], "1.2 19.1 15.9": ["deadhead"], "-5.2 12.4 12.7": ["theatergoer"], "9.0 11.6 3.3": ["largeness"], "14.1 5.0 7.3": ["bustin"], "5.4 14.0 1.3": ["swappable"], "-3.2 10.3 6.5": ["depoliticize"], "-3.0 6.8 1.8": ["exchangers"], "-0.3 -1.6 10.8": ["flannels"], "2.6 7.8 20.6": ["scull"], "9.3 11.3 12.5": ["wankers"], "3.1 1.3 1.1": ["ultrahigh"], "16.3 6.9 15.9": ["moggy"], "2.0 3.4 -2.2": ["fanzines"], "5.9 10.2 5.8": ["hysteresis"], "6.4 12.7 6.3": ["catchword"], "17.6 14.9 9.1": ["dunces"], "18.9 -0.5 4.6": ["multiscreen"], "3.1 5.5 14.6": ["overfeeding"], "6.9 10.6 7.3": ["deceivingly"], "-8.3 4.6 2.0": ["fludarabine"], "5.0 4.9 4.4": ["multifold"], "7.8 -0.1 9.5": ["nascar"], "7.0 6.5 24.8": ["midcoast"], "7.0 8.9 14.6": ["unathletic"], "4.4 17.5 24.0": ["narcissus"], "22.3 23.9 16.8": ["fricking"], "0.4 14.1 10.2": ["wastrel"], "4.4 0.6 2.2": ["clinchers"], "17.2 3.7 28.9": ["flamingoes"], "0.9 16.6 12.4": ["subtropics"], "6.5 15.0 -1.0": ["technophobe"], "2.8 3.0 33.5": ["sandpipers"], "3.9 2.9 18.9": ["riel"], "28.0 15.2 20.4": ["beanstalk"], "10.0 32.6 4.0": ["archenemies"], "5.8 13.6 28.5": ["bighead"], "-5.3 -1.4 1.8": ["encyclicals"], "3.9 0.9 7.3": ["rehouse"], "-0.6 13.2 7.3": ["obsessiveness"], "5.9 5.3 5.5": ["hoper"], "3.0 13.3 6.1": ["bumbles"], "1.5 3.9 11.8": ["densification"], "-0.8 9.4 1.4": ["tribally"], "3.1 22.3 7.7": ["fatefully"], "9.9 20.4 3.9": ["mystically"], "6.1 13.6 6.4": ["shockproof"], "5.6 -5.7 11.1": ["datebook"], "-5.9 17.7 1.7": ["misspeak"], "-1.4 10.6 3.7": ["birdying"], "17.1 17.1 10.7": ["russia"], "11.1 9.1 25.7": ["tater"], "5.1 25.4 2.5": ["fnatic"], "2.4 5.0 10.5": ["diagrammed"], "7.2 0.7 -1.9": ["shoehorning"], "2.2 6.9 10.8": ["veena"], "-4.2 0.2 4.9": ["roadworthiness"], "10.5 -0.6 7.4": ["gasfield"], "8.0 10.6 3.6": ["retune"], "3.5 6.2 0.5": ["sniffled"], "7.9 11.0 6.5": ["sulfuric"], "7.3 10.9 8.4": ["mazy"], "8.0 8.2 10.9": ["cmumusicnews"], "-1.1 2.8 4.9": ["raltegravir"], "6.3 3.1 55.0": ["seabass"], "15.7 7.3 4.7": ["wheezes"], "2.8 18.3 6.8": ["reductionism"], "6.1 21.1 25.4": ["copperhead"], "16.8 9.0 16.5": ["biff"], "2.0 7.8 11.1": ["bakkies"], "-1.7 6.8 9.7": ["weeper"], "-7.8 -4.5 -0.9": ["caesareans"], "-5.7 6.2 8.9": ["prognosticate"], "-2.2 7.4 6.8": ["mortgagor"], "-10.5 6.3 16.1": ["retrocession"], "4.3 3.6 2.8": ["misapplying"], "-2.3 -0.3 10.2": ["barre", "twohour"], "0.6 2.3 9.3": ["histopathology"], "5.1 13.2 21.2": ["martins"], "7.6 12.3 18.5": ["pangas"], "-1.4 14.0 5.7": ["strenght"], "2.8 -0.0 8.0": ["femmes"], "-5.1 6.8 4.6": ["supermoto"], "15.3 12.0 5.8": ["strewing"], "7.2 2.5 13.5": ["shortish"], "5.0 2.0 -1.1": ["initative"], "12.5 8.4 17.1": ["lanced"], "-1.2 20.4 13.4": ["middies"], "21.3 0.1 17.8": ["calabash"], "-10.4 -5.4 8.4": ["extramural"], "-3.8 13.5 3.2": ["revealingly"], "-4.8 8.7 1.4": ["nuncio"], "6.7 -0.2 5.0": ["semiprivate"], "7.2 10.5 7.7": ["inclining"], "0.9 8.7 -5.2": ["bankability"], "17.2 4.9 9.9": ["hotchpotch"], "-10.0 28.0 7.7": ["jointness"], "-2.1 15.0 5.2": ["caustically"], "4.5 4.7 8.6": ["balms"], "5.3 7.8 -0.6": ["catagory"], "8.2 11.2 7.6": ["geomagnetic"], "23.5 10.3 15.8": ["aardvark"], "2.2 -0.3 7.1": ["untradeable"], "5.3 6.7 7.9": ["witchdoctors"], "1.0 4.2 60.3": ["sablefish"], "-3.5 20.9 16.8": ["helpmate"], "-3.8 5.6 4.7": ["reinjure"], "4.5 -2.2 13.6": ["bioprocess"], "1.9 19.4 3.8": ["incontrovertibly"], "2.8 24.0 6.6": ["bioterrorist"], "-3.6 5.7 -1.5": ["rewording"], "2.2 3.8 6.5": ["sterilizer"], "2.6 12.2 11.2": ["snakebitten"], "-4.3 4.8 2.8": ["bacteremia"], "6.1 12.5 19.8": ["privet"], "-0.8 0.9 15.9": ["leanness"], "14.3 8.7 9.7": ["posthaste"], "6.3 3.6 9.5": ["milkmen", "ejemplo"], "2.7 9.6 5.8": ["coalesces"], "-5.1 2.0 5.5": ["hydrometallurgical"], "3.9 10.6 10.4": ["cometary"], "0.3 7.4 15.9": ["desalinization"], "-2.7 2.8 7.7": ["vandetanib"], "12.5 5.8 7.4": ["lounger"], "9.1 17.6 10.1": ["nincompoop"], "-3.2 3.4 -0.2": ["lev"], "-3.4 5.3 7.8": ["cohousing"], "-3.3 11.1 7.8": ["retrospection"], "2.1 8.4 10.9": ["mrs"], "-5.6 12.1 6.3": ["southeasterly"], "11.5 16.2 17.9": ["tropic"], "-4.9 -1.9 12.6": ["cigarillos"], "5.5 -4.9 -2.6": ["sorbitol"], "5.8 6.8 3.0": ["agg"], "4.4 11.8 6.2": ["theorems"], "-3.4 5.1 6.7": ["concordat"], "4.2 3.6 11.5": ["ide"], "7.4 3.3 6.9": ["strivers"], "-4.0 14.5 6.0": ["stepparent"], "8.1 11.2 13.9": ["vesicle"], "3.2 3.8 11.9": ["poojas"], "17.9 2.0 13.8": ["bitty"], "14.9 27.2 6.8": ["jetpacks"], "15.3 22.7 5.0": ["hells"], "0.2 15.5 10.9": ["skillsets"], "4.1 6.5 -1.2": ["competetive"], "3.8 7.9 39.1": ["spawners"], "6.9 12.4 8.2": ["fascinations"], "7.6 3.2 10.4": ["kyung"], "11.6 23.9 10.6": ["arsehole"], "9.2 3.6 5.0": ["formalises"], "2.3 12.4 10.7": ["darks"], "9.5 3.3 14.2": ["bloomberg"], "2.4 7.3 -0.6": ["individualization"], "0.5 2.6 9.4": ["givin"], "0.1 3.5 17.9": ["lassi"], "5.3 4.5 -0.4": ["iriver"], "-2.9 10.8 -0.7": ["pessimistically"], "-3.5 1.1 0.8": ["liaises"], "1.1 14.3 7.5": ["defroster"], "4.0 2.4 4.5": ["libre"], "21.2 5.5 9.2": ["spangly"], "-6.7 2.0 0.7": ["dysregulation"], "5.1 10.9 4.8": ["largecaps"], "-1.0 12.3 5.6": ["mispronunciation"], "-6.7 2.7 4.5": ["kumar"], "4.1 -4.0 15.4": ["bookending"], "1.3 3.2 4.8": ["jobsites", "logit"], "-0.8 4.4 6.0": ["enfranchised"], "-3.5 1.5 7.9": ["colorways"], "8.9 13.7 3.0": ["iphones"], "-1.0 -2.0 3.8": ["arrear"], "-2.9 -4.2 5.6": ["postmarketing"], "5.4 -0.7 8.4": ["cinching"], "6.7 4.4 7.1": ["michigan"], "-5.3 8.2 -0.1": ["easyhome"], "17.6 18.8 10.9": ["blowtorches"], "8.7 5.2 -0.1": ["cobbling"], "9.7 3.8 8.6": ["shatterproof"], "-2.6 13.1 17.1": ["okada"], "4.8 12.1 10.5": ["tryscoring"], "7.4 6.2 10.6": ["bobsledders"], "4.4 14.0 1.3": ["unseats"], "-5.9 13.4 -4.3": ["declarant"], "-0.1 10.7 9.4": ["sexualities"], "17.2 -4.7 16.1": ["centrepieces"], "-6.8 -1.4 9.5": ["perimenopause"], "9.2 3.0 15.8": ["gabled"], "2.7 14.9 20.8": ["liferaft"], "-2.4 5.3 0.4": ["neuroprotection", "prostone"], "9.7 9.5 21.7": ["sunless"], "-1.2 4.8 11.9": ["clonazepam"], "9.6 3.5 10.4": ["querulous"], "4.4 10.5 12.7": ["overtired"], "-5.0 13.1 14.1": ["stochastics"], "6.7 -8.1 -0.1": ["luh"], "0.6 8.7 5.5": ["counterprotesters"], "-6.4 4.8 8.0": ["upperclass"], "7.1 9.0 12.5": ["cit"], "8.8 16.7 20.3": ["cur"], "18.7 21.6 19.9": ["exoskeletons"], "5.7 18.0 13.5": ["dominions"], "-4.2 9.5 12.3": ["dollarization"], "6.5 16.2 40.4": ["gannets"], "-1.2 10.5 7.4": ["cyberinfrastructure"], "-1.7 7.1 2.6": ["msec"], "0.9 13.6 4.0": ["novelization"], "11.6 13.8 22.2": ["coolie"], "3.3 -1.2 8.6": ["sous"], "-10.3 4.4 40.5": ["chowders"], "7.7 4.0 14.5": ["hoppin"], "-6.5 9.1 2.2": ["dignifying"], "7.8 8.9 12.9": ["hothouses"], "1.1 3.7 7.1": ["missy"], "10.3 12.1 1.1": ["apparantly"], "5.9 5.5 8.1": ["vor"], "14.3 13.5 30.7": ["groper"], "-6.9 9.2 2.3": ["subluxation"], "6.3 13.4 8.0": ["forsakes"], "-1.7 9.6 6.8": ["strabismus"], "0.1 16.2 -2.5": ["sufferance"], "17.9 -0.5 12.3": ["fattens"], "2.9 3.0 12.0": ["mld"], "0.8 11.9 9.4": ["hardboiled"], "4.5 3.8 5.1": ["surau"], "-8.1 7.4 12.0": ["uncirculated"], "3.6 4.6 7.4": ["livestream"], "5.6 15.2 12.5": ["cowling"], "-5.6 7.6 2.0": ["reteaming"], "-1.6 12.9 13.0": ["overanalyzing"], "8.7 7.3 0.7": ["arabic"], "9.2 11.4 21.1": ["saguaros"], "4.1 7.3 5.7": ["sonority"], "-9.3 13.9 -1.7": ["rifampicin"], "11.0 19.5 16.2": ["crumples"], "14.5 5.2 -3.3": ["massagers"], "4.5 10.3 17.9": ["mucks"], "16.7 12.6 26.5": ["flapjack"], "7.8 11.0 10.1": ["pergolas"], "10.4 1.0 28.7": ["cajun"], "0.8 29.0 12.9": ["reticle"], "7.6 14.9 33.2": ["scabbard"], "10.4 8.0 8.0": ["posteriors"], "3.7 8.4 4.8": ["consequentially"], "-9.3 10.0 0.0": ["underdiagnosed"], "4.0 14.9 8.0": ["accutane"], "-5.9 5.7 10.2": ["judokas"], "9.7 3.4 0.8": ["thriftier"], "0.7 11.7 0.5": ["weren"], "26.7 18.8 34.5": ["anemone"], "-7.0 10.4 8.1": ["ultramarathon"], "-6.1 10.1 0.7": ["abortifacient"], "5.8 6.4 6.9": ["tre"], "8.7 -0.3 23.0": ["shipwright"], "-11.6 5.1 10.5": ["menses"], "16.2 6.6 19.8": ["mushed"], "-2.7 5.9 6.0": ["metasediments"], "11.6 -2.7 7.8": ["sidelights"], "6.5 16.6 8.0": ["mistranslation"], "-0.5 -3.6 11.0": ["skedded"], "7.9 12.9 11.4": ["gangstas"], "-3.9 -1.3 0.3": ["ultrafiltration"], "5.6 12.5 2.0": ["arduously"], "8.2 11.5 7.6": ["speedball"], "4.8 16.1 -0.6": ["intimidatory"], "15.7 6.6 12.8": ["mortarboard"], "1.7 18.8 2.8": ["mistruths"], "9.5 10.5 3.3": ["logics"], "15.3 8.8 11.3": ["suntanned"], "8.5 4.8 17.8": ["cryo"], "4.9 1.8 22.3": ["shophouses"], "6.8 3.1 0.8": ["upsizing"], "4.5 9.4 14.9": ["botanically"], "11.0 3.7 15.1": ["narcoleptic"], "-1.7 6.0 11.5": ["decadal"], "6.2 1.4 3.0": ["sys"], "3.0 6.4 6.2": ["demeanors"], "3.6 -3.0 11.2": ["biopolymer"], "16.0 18.5 9.7": ["pinpricks"], "2.3 4.1 8.2": ["pax"], "1.2 9.1 22.5": ["snowmachines"], "12.5 7.1 10.5": ["paradises"], "-2.9 9.0 6.7": ["behaviorist"], "13.0 3.0 19.6": ["poofy"], "-2.7 9.9 30.2": ["waterbirds"], "-0.4 -1.1 30.0": ["ziti"], "1.2 24.2 9.1": ["adulteress"], "13.0 14.4 5.8": ["spacetime"], "0.7 28.8 12.7": ["helo"], "-3.8 6.6 -3.1": ["avaliable"], "10.0 6.5 2.7": ["cameraphones"], "10.1 11.0 2.4": ["farrago"], "4.6 9.6 4.7": ["powersharing"], "-7.0 6.1 35.4": ["pintails"], "2.7 3.7 5.0": ["physiologists"], "4.1 1.2 5.0": ["gratings"], "-0.3 17.4 -8.9": ["defames"], "5.9 2.2 11.4": ["hairier"], "2.3 13.5 4.6": ["disgusts"], "13.2 10.5 4.5": ["cesspit"], "5.1 0.7 4.8": ["minuets"], "5.9 0.2 -2.0": ["pharmaceutics"], "-1.6 8.7 -1.0": ["dilating"], "4.2 9.2 10.7": ["alittle"], "11.1 7.0 7.0": ["playboys"], "8.8 5.3 9.7": ["glamorously"], "16.1 8.5 36.9": ["wonton"], "11.4 10.7 5.7": ["bemusing"], "-2.4 11.2 4.0": ["yatras"], "11.1 14.2 5.8": ["degeneracy"], "7.5 5.1 1.1": ["creat"], "-7.0 11.5 -0.5": ["madrasah"], "-4.9 17.9 -1.1": ["verbalizing"], "-2.1 14.5 10.6": ["pneumococcus"], "10.9 -1.0 4.2": ["ik"], "7.0 16.3 9.3": ["blabbering"], "-6.0 1.9 -5.0": ["neuropsychology"], "4.2 17.0 -2.5": ["humanise"], "6.2 1.8 10.5": ["casitas"], "8.0 0.6 3.3": ["intussusception"], "7.1 9.2 9.9": ["tach"], "12.3 12.1 12.6": ["gauchos"], "1.7 11.6 6.8": ["dyslexics"], "-6.5 4.8 -2.9": ["consensually"], "17.5 9.2 5.6": ["absentmindedly"], "-3.3 6.9 0.7": ["truncating"], "8.1 4.5 3.4": ["skittling"], "7.0 2.8 6.8": ["lu"], "0.3 12.2 5.5": ["punctually"], "4.4 5.6 10.1": ["hector"], "11.8 8.4 14.6": ["frappes"], "7.0 3.5 4.1": ["unfastened"], "10.9 -0.8 -2.2": ["sah"], "13.2 9.2 10.6": ["oche"], "7.2 10.3 0.1": ["scientology"], "-8.6 4.6 -2.6": ["dopaminergic"], "3.4 -1.1 17.0": ["noni"], "4.4 5.1 8.9": ["gam"], "2.2 4.6 11.2": ["frontages"], "1.7 8.6 -2.9": ["deprecation"], "0.6 6.3 32.5": ["northerns"], "9.5 14.0 26.4": ["forager"], "5.3 0.6 12.1": ["filmfest"], "6.7 -3.7 6.7": ["plastination"], "-8.0 -4.4 12.0": ["naturopaths"], "12.7 13.4 2.3": ["messiahs"], "3.1 16.2 0.8": ["gloried"], "-6.3 22.2 0.8": ["amir"], "1.8 11.9 10.0": ["overstays"], "11.1 2.6 6.7": ["este"], "5.8 2.6 2.2": ["progess"], "-5.5 1.4 -2.2": ["signalization"], "1.7 4.5 5.3": ["suctioning"], "2.6 15.3 10.3": ["solipsism"], "3.3 11.3 4.2": ["mispronounce"], "30.0 9.3 15.4": ["lego"], "5.6 -7.2 7.7": ["gsm"], "9.1 10.4 9.3": ["babbles"], "11.5 13.3 9.4": ["dogpile"], "-13.0 1.0 0.8": ["salutatorians"], "1.8 11.2 4.5": ["debases"], "3.4 16.1 8.5": ["reciprocally"], "9.6 17.7 1.2": ["communistic"], "-4.2 9.7 9.5": ["purser"], "11.1 -5.9 1.4": ["wranglings"], "-1.6 -2.0 8.2": ["genotyped"], "0.4 6.4 6.5": ["spaceflights"], "-1.3 13.3 17.6": ["pizzicato"], "-3.5 9.4 5.4": ["qawwali"], "0.5 6.5 1.4": ["privies"], "-7.3 11.7 10.9": ["comradery"], "-2.1 8.1 10.8": ["campouts"], "1.8 2.6 6.4": ["recessional"], "-3.2 6.7 12.6": ["weatherstripping"], "-0.7 5.5 9.5": ["lipoproteins"], "7.1 2.6 5.2": ["twigged"], "7.6 7.2 11.2": ["rhumba"], "0.8 4.9 9.2": ["floormats"], "-6.3 6.4 2.0": ["multifactorial"], "1.4 0.5 7.5": ["vlogs"], "4.7 14.0 23.5": ["bolo"], "13.6 3.6 5.6": ["brazil"], "-0.0 1.6 4.3": ["psig"], "-3.4 3.9 4.1": ["orebodies"], "0.2 16.0 15.1": ["bleeder"], "0.0 7.3 6.9": ["potentiometer"], "-3.4 11.9 13.3": ["kickout"], "14.6 7.2 12.5": ["bastardization"], "-4.0 12.9 5.2": ["verity"], "3.2 19.7 0.8": ["unindicted"], "3.0 2.9 1.4": ["peruses"], "0.5 4.9 7.4": ["goss"], "6.3 6.4 9.6": ["opencast"], "5.8 5.7 9.5": ["firepit"], "-0.2 0.6 7.6": ["tensioning"], "1.9 14.1 13.2": ["necessaries"], "9.8 17.8 5.8": ["codenames"], "8.1 26.2 7.1": ["codeword"], "8.2 -4.9 3.3": ["esta"], "0.6 -0.8 16.8": ["spirulina"], "8.0 10.2 13.4": ["garret"], "-5.0 -1.0 7.9": ["rehousing"], "10.1 9.7 8.2": ["gobbledegook"], "17.1 -1.1 13.8": ["surfwear"], "3.6 -0.6 3.9": ["oe"], "9.1 16.4 28.1": ["cannas"], "8.3 15.9 17.1": ["earths"], "6.4 14.2 3.2": ["unrelieved"], "16.4 19.0 14.6": ["troglodytes"], "4.2 6.6 13.3": ["beiges"], "1.0 8.0 18.3": ["siders"], "9.4 6.9 4.9": ["metalworker"], "10.8 1.4 7.0": ["bluejeans"], "2.9 9.9 22.7": ["rafted"], "8.7 0.2 0.6": ["sept"], "9.9 3.0 38.1": ["panko"], "4.6 1.6 7.0": ["biosurgery"], "-2.4 6.5 15.0": ["tanzanite"], "12.2 7.3 8.3": ["diya"], "-3.0 3.1 6.2": ["surcharged"], "4.7 1.5 3.9": ["webhosting"], "23.4 14.8 19.4": ["mousetraps"], "17.5 12.4 6.9": ["moneymen"], "4.0 0.1 1.9": ["triallists"], "-4.6 13.7 -0.4": ["discerns"], "11.4 8.7 -0.3": ["mesmerise"], "-2.1 9.0 7.8": ["severances"], "1.5 15.7 9.3": ["botulinum"], "22.1 15.5 13.6": ["vaster"], "20.2 34.2 20.4": ["orc"], "7.5 -1.9 10.3": ["caftan"], "-11.5 1.0 3.2": ["telefilms"], "3.8 12.7 7.1": ["nincompoops"], "6.1 7.1 6.8": ["backheeled"], "17.9 -1.3 4.0": ["removers"], "19.4 14.0 2.9": ["transmogrified"], "1.1 -1.5 10.4": ["pastured"], "10.8 -0.0 13.7": ["woodcarvings"], "16.2 16.7 2.1": ["idiotically"], "16.6 8.2 11.3": ["drools"], "3.5 1.2 7.9": ["slipcase"], "3.8 0.3 -0.3": ["hearkened"], "8.1 1.5 1.5": ["reamed"], "0.3 1.4 13.0": ["teashop"], "10.3 7.4 1.2": ["clutters"], "-5.6 16.2 13.5": ["predestination"], "-6.1 -1.0 10.8": ["tmcft"], "3.5 -0.4 2.5": ["bandying"], "0.6 7.8 12.8": ["sarah"], "10.7 -1.2 16.6": ["lino"], "22.6 9.7 16.5": ["undulate"], "9.7 -3.0 17.0": ["refectory"], "9.0 5.7 9.7": ["unbolted"], "11.6 10.3 9.1": ["shagged"], "10.9 4.3 27.3": ["horsemeat"], "-6.3 10.8 11.4": ["rejoinders"], "-2.4 9.3 10.3": ["graininess"], "6.0 6.0 7.3": ["flashiness"], "13.0 9.8 12.0": ["hailstone"], "9.7 6.3 6.4": ["launderette"], "-0.5 9.2 -1.3": ["priviledge"], "-1.2 1.7 -3.7": ["remarketed"], "3.0 16.2 0.5": ["agianst"], "-5.5 3.3 4.1": ["cardiothoracic"], "-1.8 8.4 2.4": ["printheads"], "-4.9 4.0 6.6": ["ranibizumab"], "-1.4 1.5 3.7": ["dosimetry"], "2.9 13.0 3.4": ["unprovable"], "-2.3 14.8 6.1": ["sence"], "1.6 15.1 11.9": ["wadis"], "3.1 8.1 5.4": ["theobromine"], "3.2 9.0 8.3": ["engravers"], "3.0 6.6 9.0": ["semicolon"], "6.1 12.6 8.2": ["stanching"], "2.6 -5.8 -4.5": ["chg"], "3.7 12.0 16.5": ["moonshiners"], "16.2 12.7 10.5": ["aerostat"], "8.4 3.6 3.8": ["scribed"], "-3.5 6.7 9.1": ["xeriscaping"], "9.7 35.8 4.2": ["kafirs"], "1.8 1.6 7.7": ["unrequested"], "8.7 2.7 29.6": ["tortas"], "10.5 5.9 7.5": ["overprice"], "8.7 6.2 9.1": ["mk"], "6.8 9.6 4.7": ["everbody"], "-7.8 2.0 13.4": ["lees"], "12.4 14.4 10.3": ["sullenly"], "8.5 7.0 18.0": ["rummy"], "7.2 4.2 -0.5": ["offically"], "2.6 2.0 17.5": ["diggings"], "19.4 8.2 17.6": ["shakey"], "7.2 3.2 15.5": ["toile"], "9.8 6.9 9.6": ["unamused"], "-0.3 12.4 31.5": ["escapement"], "-8.0 2.0 6.9": ["hydrochlorothiazide"], "13.9 -3.1 2.0": ["worldclass"], "13.5 9.7 8.4": ["det"], "2.2 8.3 22.4": ["windsurf"], "-1.4 10.1 9.8": ["proprietorship"], "7.4 13.9 6.1": ["shirks"], "5.9 0.1 16.6": ["swishy"], "3.4 10.2 7.0": ["midsole"], "6.1 -0.3 13.0": ["negligee"], "6.8 10.2 8.8": ["shopfloor"], "-5.1 4.0 7.3": ["deanship"], "3.1 16.3 8.6": ["embargos"], "-6.7 2.4 13.0": ["yeses"], "12.2 4.1 4.7": ["msn"], "3.4 10.7 10.2": ["birthmarks"], "8.8 25.2 16.5": ["assumedly"], "10.2 10.4 23.8": ["strainers"], "-10.4 -2.5 9.6": ["geriatricians"], "-4.8 5.7 8.3": ["immunologists"], "13.7 5.4 4.8": ["flameouts"], "-3.7 6.7 6.9": ["comedically"], "11.0 8.7 15.8": ["unitard"], "2.6 -1.9 17.4": ["microplate"], "7.4 27.5 10.7": ["nato"], "9.1 13.0 0.9": ["exploitations"], "5.2 9.0 20.6": ["colouration"], "3.2 25.4 4.5": ["dogmatically"], "-0.4 13.0 6.3": ["bathos"], "0.7 9.2 9.3": ["trances"], "7.8 10.1 25.0": ["merlin"], "-8.3 2.9 -0.7": ["silane"], "1.4 2.4 8.1": ["upcycle"], "4.7 10.9 17.9": ["midlanders"], "-8.8 2.9 0.7": ["dabigatran"], "18.4 6.7 9.7": ["roughnecks"], "-8.1 9.8 -0.0": ["preoperatively"], "3.8 13.8 6.3": ["witticism"], "6.0 1.1 3.5": ["olefin"], "1.4 5.5 1.5": ["stylishness"], "-2.9 5.1 11.3": ["reffing"], "10.0 6.4 10.4": ["stockman"], "12.2 5.0 7.1": ["nudie"], "15.4 6.3 11.2": ["uncorks"], "2.1 10.2 1.0": ["protestation"], "1.8 3.8 4.0": ["nanobiotechnology"], "15.3 12.1 26.5": ["ficus"], "0.7 9.9 4.6": ["entrapments"], "3.5 13.1 6.8": ["caricaturing"], "5.6 4.2 2.7": ["parcours"], "-1.0 0.5 14.7": ["measurers"], "-1.8 7.1 -5.1": ["antiperspirants"], "7.2 3.4 32.3": ["cannelloni"], "-0.3 16.9 24.0": ["viburnum"], "12.0 10.0 14.2": ["nursemaid"], "4.7 12.4 8.6": ["cohabitate"], "3.1 13.4 15.6": ["coitus"], "-2.0 15.6 11.1": ["patroller"], "-0.9 23.0 2.1": ["dishearten"], "9.2 2.3 9.2": ["ks"], "8.4 0.9 11.5": ["seattle"], "-10.1 25.6 5.9": ["enlistee"], "-7.3 4.4 2.8": ["redetermination"], "4.9 4.1 7.2": ["linkers"], "22.2 7.7 11.0": ["paperclips"], "5.7 2.2 25.3": ["chu"], "-3.1 7.2 1.3": ["proscribing"], "-3.9 8.2 5.0": ["contralateral"], "-7.2 8.7 9.1": ["interferons"], "4.4 6.5 11.5": ["funkiness"], "6.9 13.1 14.9": ["roughhouse"], "14.4 -2.6 15.5": ["pleather"], "-3.4 11.6 8.8": ["moisturise"], "3.7 7.6 3.9": ["pressman"], "-7.1 -7.6 2.9": ["honorariums"], "16.7 3.8 9.0": ["salesgirl"], "13.2 12.1 3.8": ["abseiled"], "7.1 2.6 -0.4": ["whelmed"], "9.3 12.2 26.6": ["goldfinch"], "-1.0 -3.9 3.0": ["reanalysis"], "6.0 -7.1 2.0": ["annum"], "2.1 2.2 23.1": ["basswood"], "8.3 4.7 11.1": ["bumptious"], "13.8 38.1 16.3": ["redcoats"], "5.7 -1.4 10.9": ["bd"], "17.0 0.8 12.8": ["pimply"], "10.2 8.2 6.8": ["bullocking"], "7.7 -3.7 6.1": ["scotches"], "3.9 9.0 0.3": ["debugged"], "3.7 12.8 8.7": ["lithology"], "11.6 14.8 20.6": ["woodcutter"], "1.9 2.6 10.8": ["momento"], "-2.7 19.6 37.3": ["artificials"], "7.9 11.3 30.3": ["delectably"], "-9.5 9.0 12.4": ["completists"], "-2.4 9.1 8.5": ["asynchronously"], "3.5 5.3 5.4": ["hirers"], "-0.9 6.7 24.4": ["litchi"], "-1.6 6.7 6.1": ["demodulation"], "11.3 20.1 17.9": ["copulate"], "-1.1 10.2 6.5": ["justin"], "6.6 12.2 4.3": ["misgovernance"], "2.5 1.7 -2.7": ["vc"], "3.9 15.1 12.5": ["pumas"], "-1.3 -3.2 5.0": ["passbooks"], "5.9 20.7 11.0": ["tautology"], "0.2 22.4 -1.2": ["disengages"], "-5.0 5.6 5.5": ["apportions"], "10.7 6.5 18.5": ["nipper"], "7.2 3.8 19.3": ["toonie"], "-9.0 15.1 8.3": ["preventively"], "1.2 4.8 13.5": ["schoolbus"], "3.6 7.3 8.7": ["shud"], "5.2 16.2 20.0": ["suplexes"], "8.6 3.3 6.1": ["unlicenced"], "-2.5 3.1 13.0": ["telemark"], "-10.3 8.8 9.4": ["theatergoing"], "8.0 16.1 7.4": ["declaimed"], "9.7 10.2 8.2": ["amplitudes"], "6.4 8.9 14.9": ["harems"], "-4.7 5.1 3.4": ["perchlorethylene"], "1.6 3.9 6.7": ["wright"], "0.6 -2.2 30.3": ["canners"], "15.2 1.0 11.2": ["slatted"], "11.2 11.7 8.1": ["larking"], "5.7 9.8 11.9": ["enviromental"], "-2.0 14.2 10.5": ["statelessness"], "7.3 11.3 10.9": ["talls"], "6.5 -1.2 14.6": ["marmosets"], "11.5 8.9 13.8": ["sightscreen"], "2.0 -3.1 0.5": ["rigourous"], "4.0 11.6 5.3": ["fanbases"], "8.4 -0.8 11.7": ["toronto"], "8.0 1.1 7.2": ["overlain"], "-5.4 9.7 2.9": ["imputing"], "7.1 3.4 13.6": ["sickies"], "-1.3 16.9 8.7": ["jumpshots"], "5.2 11.2 17.6": ["ladling"], "0.2 7.2 4.5": ["spudding"], "16.8 23.6 26.7": ["millipedes"], "-0.7 5.9 21.0": ["jowar"], "9.7 2.9 17.9": ["wreathes"], "-0.0 9.5 7.6": ["felsic"], "6.1 6.5 35.9": ["julienne"], "27.2 8.4 2.1": ["demerging"], "20.4 8.2 18.1": ["waddles"], "6.9 -4.7 9.1": ["septuagenarians"], "3.6 10.8 8.7": ["infarct"], "1.4 9.4 1.0": ["pontificates"], "8.5 5.9 14.1": ["sulfurous"], "3.6 7.8 9.7": ["pimpin", "squibbed"], "-11.0 0.3 10.2": ["deanery"], "6.7 6.9 11.6": ["embezzlers"], "13.3 9.5 14.5": ["fleck"], "6.6 7.8 27.6": ["rinds"], "5.4 4.5 11.2": ["gud"], "31.7 10.2 12.1": ["thingie"], "7.7 -0.1 20.7": ["tiffin"], "1.5 7.5 6.3": ["coprocessor"], "3.4 8.3 14.2": ["cosmopolitans"], "-2.3 11.8 1.5": ["superset"], "2.1 27.4 7.1": ["minutemen"], "1.7 10.5 8.7": ["polyphenol"], "14.4 -1.8 20.4": ["stuffer"], "13.1 13.8 18.9": ["yokel"], "2.8 7.4 5.6": ["ous"], "-3.8 14.2 6.0": ["retellings"], "4.0 9.5 24.2": ["greenstone"], "6.2 13.2 12.3": ["polyrhythmic"], "-0.7 13.1 -0.4": ["punitively"], "-4.7 5.0 3.8": ["overdubbing"], "4.8 4.7 -0.7": ["spiritualists"], "9.7 9.4 10.3": ["fluffs"], "0.2 16.8 13.5": ["blowdown"], "11.9 13.0 13.7": ["scabrous"], "1.0 13.8 11.0": ["newspapermen"], "4.6 34.9 5.5": ["battlefronts"], "17.2 12.4 5.6": ["centricity"], "17.7 13.4 21.1": ["battens"], "3.0 5.3 20.8": ["subduction"], "-5.2 8.8 3.6": ["perfumers"], "0.7 35.8 12.7": ["belligerency"], "7.2 14.4 10.3": ["southeastward"], "-5.4 7.1 8.8": ["bhajan"], "-1.9 1.3 10.5": ["waterpolo"], "6.9 4.6 7.5": ["thickeners"], "14.7 11.8 39.2": ["draggers"], "11.1 -1.7 7.2": ["careworn"], "15.2 13.9 5.0": ["thrum"], "8.8 10.2 11.8": ["pharynx"], "0.7 4.0 4.9": ["aliskiren"], "3.3 5.1 9.8": ["aminopterin"], "11.2 6.8 10.1": ["minces"], "11.1 6.3 5.4": ["sexagenarian"], "-5.0 13.3 8.1": ["sentimentalism"], "7.5 10.8 13.3": ["riotously"], "9.1 10.4 25.7": ["buzzbaits"], "7.2 16.7 20.8": ["landward"], "17.2 19.2 9.8": ["uproots"], "13.7 16.7 7.5": ["irresistable"], "8.1 7.7 11.5": ["buzzkill"], "0.7 -1.4 11.9": ["afters"], "3.6 4.6 -0.9": ["netballer"], "-3.9 8.4 11.6": ["clonal"], "9.1 29.0 5.7": ["tormenters"], "6.6 8.1 1.6": ["erasable"], "6.7 -0.4 11.9": ["springlike"], "1.3 11.3 13.5": ["overcautious"], "-10.6 13.2 5.8": ["voluntariness"], "12.4 2.5 43.6": ["daikon"], "-2.9 11.6 7.6": ["adsorbed"], "12.2 -2.3 3.3": ["bouyed"], "-0.5 14.2 10.6": ["batsmanship"], "21.6 9.0 25.4": ["anteater"], "3.9 6.0 15.4": ["mets"], "12.4 24.4 15.1": ["glower"], "5.5 4.2 8.0": ["hispanics"], "-1.3 5.1 3.8": ["femtosecond"], "3.8 12.2 4.1": ["sceneries"], "8.8 -2.2 1.9": ["misspelt"], "4.6 2.1 15.6": ["thighbone"], "3.1 2.6 8.1": ["naphthalene"], "16.3 0.1 11.5": ["inital"], "-4.2 5.8 -0.3": ["congesting"], "5.0 24.8 2.1": ["persecutes"], "6.3 5.0 13.9": ["downtick"], "-3.5 -5.2 8.8": ["cystinosis"], "10.2 8.0 14.0": ["bogan"], "11.7 0.6 18.6": ["slopped"], "0.5 1.8 44.2": ["fiddleheads"], "22.2 22.6 14.9": ["anvils"], "-5.6 -5.9 1.7": ["finshed"], "5.5 17.2 5.5": ["preponderant"], "9.9 13.1 12.0": ["bearhug"], "11.8 22.1 15.0": ["meddlers"], "5.2 3.3 14.4": ["muy"], "14.2 25.4 6.7": ["desperado"], "2.6 -0.1 -1.8": ["ethnomusicology"], "0.1 15.5 16.3": ["demarcations"], "7.9 13.4 10.4": ["profanely"], "8.9 9.8 3.2": ["coruscating"], "9.8 7.5 28.0": ["puffer"], "15.4 13.9 22.8": ["saguaro"], "15.7 9.8 7.2": ["phenomenons"], "16.2 -0.0 2.5": ["esure"], "13.1 2.6 11.1": ["ker"], "-3.2 0.2 28.3": ["fuchsias"], "4.3 5.6 -0.5": ["megasite"], "-1.0 2.8 16.6": ["vitrification"], "14.4 20.2 14.4": ["hovercrafts"], "14.1 22.2 8.4": ["daemons"], "10.5 11.5 4.4": ["undreamed"], "-0.8 4.9 9.9": ["punishingly"], "10.3 11.0 12.7": ["regolith"], "4.8 11.5 2.1": ["conformal"], "-2.8 11.8 8.5": ["campesino"], "-2.5 0.8 2.5": ["invovled"], "13.1 10.1 22.4": ["payline"], "3.1 -1.9 8.6": ["boleros"], "-3.6 0.9 7.0": ["glia"], "5.7 13.4 -0.9": ["echos"], "12.3 -4.5 3.7": ["centerstage"], "12.9 15.7 7.2": ["unscrupulously"], "-0.7 4.9 11.0": ["frats"], "-6.7 4.0 6.0": ["garaged"], "23.4 8.8 11.9": ["petrochem"], "-10.7 7.8 -4.2": ["facilitative"], "2.1 9.3 2.1": ["promulgates"], "-0.3 6.6 3.7": ["nagar"], "11.8 9.1 4.9": ["direly"], "1.1 10.1 6.7": ["photodiodes"], "2.5 2.8 9.0": ["coronations"], "-6.0 -1.1 2.7": ["unselected"], "11.6 8.2 9.4": ["bucketload"], "0.2 4.0 1.7": ["vaporizers"], "1.5 7.3 15.9": ["nurseryman"], "25.8 6.3 17.2": ["maypole"], "1.9 -2.8 7.4": ["ossuaries"], "-0.6 5.1 5.5": ["vulcanologist"], "0.1 9.1 3.6": ["bridleway"], "-4.8 7.8 11.6": ["precip"], "-0.0 8.3 12.9": ["soffits"], "10.6 0.3 1.9": ["servos"], "4.6 28.2 10.2": ["shibboleth"], "13.0 6.2 25.7": ["passionfruit"], "13.0 2.6 1.4": ["hypertext"], "14.7 3.2 -3.6": ["trainload"], "-0.9 9.9 8.3": ["undercards"], "10.2 6.4 24.1": ["terrariums"], "11.8 -3.0 13.5": ["barrettes"], "2.9 8.2 5.4": ["sorrier"], "5.9 12.0 13.6": ["archaea"], "23.0 5.7 11.5": ["foodmakers"], "-0.9 12.8 7.8": ["yaar"], "18.7 12.6 6.2": ["unfixable"], "-11.9 4.0 8.0": ["recusals"], "3.7 5.3 -4.8": ["adress"], "1.9 17.3 5.8": ["entrapping"], "4.0 -4.7 -5.0": ["cluding"], "-4.7 8.2 9.3": ["ferroalloy"], "13.3 5.8 4.0": ["flyin"], "-3.1 4.8 8.6": ["walkovers"], "-5.3 -2.3 6.4": ["encashment"], "2.1 6.5 5.1": ["mbira"], "22.2 12.1 10.7": ["copulating"], "14.4 2.9 5.1": ["inhalable"], "-0.7 4.1 -2.7": ["encomiums"], "-1.9 8.5 4.9": ["constrictive"], "-2.4 6.2 7.9": ["transaxle"], "14.8 8.4 21.4": ["nog"], "2.3 6.6 2.6": ["supercapacitor"], "17.7 7.3 11.2": ["seesaws"], "-6.9 2.9 3.1": ["netlist"], "6.1 3.1 3.6": ["reassumed"], "-2.6 8.8 7.3": ["bumetanide"], "10.2 18.0 11.6": ["yowling"], "13.5 3.1 14.2": ["scuppers"], "3.8 24.5 5.6": ["zionist"], "-5.1 3.4 9.5": ["paydowns"], "-6.5 5.7 7.8": ["exemestane"], "-4.8 5.5 5.5": ["phenoxodiol"], "6.1 21.7 4.5": ["rightwingers"], "-8.7 7.9 1.0": ["paraplegia"], "3.3 9.7 10.4": ["uninstaller"], "-0.4 3.1 15.7": ["nontribal"], "2.2 -3.8 6.3": ["dans"], "19.5 6.3 7.9": ["playland"], "17.3 -2.2 13.0": ["foldout"], "17.9 7.9 33.8": ["stockpot"], "14.8 -1.7 28.6": ["doily"], "13.4 11.8 13.2": ["woofing"], "1.7 10.4 14.6": ["spacings"], "11.3 10.8 19.7": ["bratwursts"], "-6.8 8.9 4.4": ["convalesce"], "11.9 6.5 17.1": ["boules"], "20.8 10.3 13.7": ["pinheads"], "9.3 3.9 10.1": ["alcopop"], "-1.9 12.3 -4.1": ["bidistrict"], "0.6 8.9 19.9": ["prepositions"], "6.7 11.3 15.1": ["awww"], "13.1 2.7 21.0": ["cheeked"], "-4.9 0.4 4.9": ["reword"], "13.8 12.7 7.4": ["shitload"], "1.1 13.1 25.3": ["ungulates"], "-1.5 6.7 -0.5": ["lubricity"], "-3.6 0.6 9.3": ["pharyngitis"], "5.9 4.6 0.4": ["hankered"], "4.5 15.5 19.5": ["procreating"], "6.8 14.2 7.1": ["disdaining"], "1.9 21.9 4.4": ["disempowering"], "7.7 -0.9 16.8": ["ster"], "8.6 17.3 4.4": ["muckraker"], "-0.1 19.7 7.0": ["detraction"], "3.1 7.8 6.1": ["detailer"], "1.9 -0.4 12.0": ["relining"], "1.2 3.0 17.7": ["sinter"], "6.1 3.2 12.5": ["wiht"], "18.2 15.0 16.0": ["boneheads"], "14.4 12.1 2.0": ["immortalizing"], "7.4 4.9 16.4": ["undecorated"], "3.8 7.8 6.9": ["noteholder"], "9.3 3.9 7.5": ["nanodevices"], "6.8 -5.7 11.4": ["dna"], "8.8 28.7 14.7": ["starships"], "4.6 1.3 11.6": ["satiating"], "-10.4 -0.7 1.7": ["remands"], "-4.6 10.9 1.0": ["overzealousness"], "11.2 22.1 4.5": ["nihilists"], "2.7 13.2 1.7": ["upbraiding"], "5.0 11.2 20.3": ["shovelers"], "4.9 4.9 0.6": ["experimentations"], "2.9 -0.0 3.0": ["injectible"], "1.1 5.7 6.2": ["lll"], "-2.2 4.4 -2.3": ["kilovolts"], "5.3 12.9 9.2": ["jests"], "1.5 3.8 10.1": ["slackens"], "7.4 2.7 13.3": ["jowly"], "-2.4 4.7 6.6": ["codon"], "7.2 10.2 -5.7": ["democratised"], "5.1 6.7 43.3": ["mako"], "2.2 29.7 4.6": ["miltary"], "5.8 15.3 12.8": ["heartedly"], "9.1 0.2 9.6": ["ade"], "24.0 19.0 18.1": ["zapper"], "-0.3 11.4 3.6": ["watchhouse"], "5.7 -3.3 2.8": ["loooong"], "3.5 4.8 13.5": ["piquancy"], "4.0 3.4 4.8": ["bac"], "5.3 13.9 -0.3": ["christianity"], "6.2 2.4 2.1": ["greenlighting"], "10.6 2.3 6.3": ["hellraiser"], "0.8 10.5 7.3": ["bushwalking"], "15.1 18.0 5.5": ["reincorporate"], "4.9 0.9 4.5": ["skullcaps"], "-0.7 2.2 20.5": ["packinghouse"], "2.6 10.4 7.0": ["devasted"], "13.2 15.7 10.4": ["homogenizing"], "2.4 6.4 11.3": ["grandmom"], "2.6 1.8 -0.2": ["ytd"], "-2.0 15.2 4.0": ["kidnaping"], "3.2 17.1 9.4": ["flagstand"], "2.1 0.0 10.0": ["cystitis"], "6.2 3.8 10.7": ["sousaphone"], "-0.3 8.1 7.2": ["terminalling"], "3.3 14.9 25.5": ["overexploited"], "2.1 21.4 -2.8": ["surveil"], "2.5 8.7 2.4": ["incisiveness"], "19.0 19.5 8.4": ["semaphore"], "13.5 1.2 -3.4": ["hairdryers"], "5.5 17.9 -0.2": ["foments"], "-2.8 0.4 1.6": ["asknet"], "13.0 16.8 9.3": ["beauteous"], "7.9 -4.1 6.5": ["fundraisings"], "4.4 -7.7 1.7": ["cations"], "0.5 8.2 0.1": ["nightclothes"], "4.9 3.7 7.5": ["ontologies"], "-8.6 3.9 6.9": ["tardies"], "-4.5 6.5 11.9": ["jewelries"], "9.5 7.8 2.7": ["spraypainted"], "-0.0 20.6 7.2": ["dismounts"], "11.8 10.8 15.4": ["harridan"], "-2.7 7.8 14.5": ["phytochemical"], "0.3 0.9 8.5": ["channelized"], "5.0 4.5 10.4": ["dallas"], "9.6 8.2 14.2": ["cummerbund"], "-6.6 -2.3 -1.3": ["discontinuations"], "-4.7 4.0 17.9": ["oaky"], "5.2 0.4 -1.5": ["facilties"], "4.8 19.5 -0.9": ["vanguards"], "-1.2 8.6 9.5": ["waspish"], "10.1 7.4 6.0": ["jumbles"], "3.3 6.0 7.0": ["suffragists"], "-4.6 5.4 2.3": ["torques"], "13.7 20.9 12.1": ["camouflages"], "1.7 1.3 16.7": ["gutkha"], "-9.8 6.8 3.2": ["adalimumab"], "0.4 4.1 10.3": ["godchild"], "9.7 0.4 0.8": ["verantwortlich"], "10.7 4.2 6.9": ["mooing"], "-5.9 7.6 7.9": ["geting"], "18.3 9.5 32.9": ["oceangoing"], "10.0 18.2 7.4": ["ineluctable"], "6.6 12.0 17.7": ["gennaker"], "2.8 7.4 17.7": ["mildness"], "4.3 9.3 8.7": ["shying"], "3.1 -3.1 10.2": ["fuh"], "3.7 4.8 9.3": ["sitemap"], "13.1 6.3 14.7": ["unscrambled"], "13.1 -2.2 10.8": ["fiftysomething"], "10.3 7.2 19.2": ["transoceanic"], "10.4 11.6 8.3": ["hahahaha"], "12.9 27.2 4.5": ["annihilates"], "11.9 11.7 20.5": ["dockyards"], "15.0 3.0 3.3": ["highspeed"], "13.5 4.6 11.7": ["homogenised"], "3.9 11.3 3.7": ["troublingly"], "-10.4 20.5 5.1": ["flyable"], "8.7 4.1 18.3": ["flagstones"], "-2.0 4.8 3.5": ["admited"], "-1.8 8.4 9.2": ["brooked"], "-9.0 12.0 8.8": ["basehit"], "-0.7 7.2 14.0": ["tayo"], "28.5 9.3 24.9": ["triceratops"], "11.1 14.2 3.8": ["refuels"], "-2.1 5.2 26.0": ["fenugreek"], "0.3 6.6 11.5": ["jesting"], "12.5 7.3 16.9": ["spackle"], "0.5 20.4 6.6": ["quiescence"], "15.4 4.9 8.5": ["pealing"], "-10.4 11.7 -1.0": ["triable"], "1.4 10.7 9.8": ["unconsidered"], "-5.3 5.5 9.4": ["digressing"], "-8.1 20.1 7.6": ["jirgas"], "12.8 5.5 23.1": ["blackish"], "5.8 6.9 9.6": ["groovin"], "-0.4 13.1 9.0": ["abdicates"], "16.4 4.4 19.7": ["toboggans"], "14.8 27.1 17.0": ["wrathful"], "14.8 6.0 -3.2": ["touchless"], "0.1 0.7 11.8": ["dapat"], "8.4 6.3 7.7": ["crating"], "8.9 9.2 26.2": ["icehouse"], "-4.0 7.2 7.6": ["hemolysis"], "8.2 -6.2 13.5": ["cryonics"], "12.3 22.0 10.3": ["unsheathed"], "14.9 10.0 -5.3": ["aquire"], "11.9 12.3 9.5": ["undergirds"], "16.3 14.6 11.3": ["despoiling"], "1.2 1.5 11.0": ["cole"], "3.7 12.4 5.7": ["drolly"], "21.3 10.5 31.7": ["whiskered"], "6.1 10.0 10.6": ["nec"], "-3.2 10.4 4.1": ["sati"], "4.4 7.1 14.9": ["gapper"], "20.0 11.8 17.9": ["snaky"], "3.0 4.8 2.6": ["nasopharyngitis"], "4.4 3.4 4.3": ["mandolinist"], "5.0 -0.2 9.5": ["furrier"], "2.3 5.5 14.3": ["stallholder"], "15.8 15.1 19.4": ["tyrannosaurs"], "11.6 4.6 10.9": ["goosing"], "18.5 5.7 14.8": ["calliope"], "-0.5 7.3 8.8": ["rakeback"], "-6.4 4.7 9.8": ["laicization"], "-4.8 1.8 2.9": ["subacute"], "9.8 1.5 3.3": ["hyperextending"], "9.2 16.1 14.6": ["israelinsider"], "12.1 9.1 2.7": ["uppercase"], "16.4 10.3 7.4": ["burghers"], "0.4 11.6 7.4": ["copout"], "6.0 -2.6 6.4": ["joon"], "5.6 1.4 30.2": ["caramelised"], "4.2 -1.4 15.3": ["argyle"], "-15.4 1.0 15.5": ["carryovers"], "-9.2 16.2 -2.7": ["countermanded"], "2.7 39.5 12.8": ["kamikazes"], "7.5 10.1 26.9": ["sedges"], "-1.2 -0.3 5.3": ["ary"], "5.5 -1.7 8.2": ["laminator"], "14.1 6.8 5.4": ["asthe"], "7.4 9.3 9.5": ["pucca"], "21.0 10.7 8.2": ["beermaker"], "4.4 12.0 5.6": ["mystification"], "2.4 -4.7 16.8": ["tempera"], "2.7 14.5 5.1": ["sublimate"], "1.9 11.5 29.5": ["quagga"], "7.7 21.9 12.3": ["volleyer"], "-1.0 -0.7 -9.2": ["microturbine"], "7.5 5.0 4.1": ["taxies"], "6.1 13.0 -0.1": ["unventilated"], "-5.7 10.8 4.6": ["precipitations"], "11.5 17.1 6.6": ["pinko"], "-1.5 5.6 9.4": ["dormer"], "5.4 3.8 19.4": ["sculls"], "0.5 4.8 7.4": ["vends"], "4.9 6.0 20.2": ["myosin"], "12.7 6.2 7.7": ["fanfares"], "10.7 6.1 5.8": ["purveying"], "2.8 9.3 44.6": ["pintail"], "7.3 4.6 17.1": ["scratchings"], "-1.3 6.9 2.3": ["carryback"], "1.4 8.0 15.0": ["anthocyanin"], "3.2 9.9 13.3": ["pommel"], "20.6 13.9 15.9": ["faun"], "5.7 8.4 7.0": ["concious"], "5.8 3.9 12.4": ["microsatellite"], "-3.3 5.2 2.4": ["muftis"], "-1.5 -1.0 -3.6": ["milli"], "1.5 0.7 7.0": ["reinvestments"], "4.7 11.7 10.0": ["tantrik"], "10.8 1.7 21.0": ["meatworks"], "11.4 24.1 2.0": ["enslaves"], "6.9 -2.2 1.8": ["nounced"], "-0.9 7.0 3.4": ["manged"], "3.0 3.5 6.7": ["hematopoietic"], "8.9 11.0 25.0": ["oarsman"], "7.5 1.8 8.2": ["raver"], "-1.7 1.7 10.4": ["futurity"], "-3.4 16.1 17.7": ["overwatering"], "10.0 5.0 4.3": ["auguring"], "-2.0 7.1 5.1": ["referrers"], "11.6 14.1 16.1": ["thumbtacks"], "8.0 11.2 21.9": ["pinkies"], "1.5 -1.8 5.5": ["flowmeters"], "-4.1 5.7 9.5": ["radionuclide"], "-3.4 4.7 10.7": ["toremifene"], "8.4 5.7 5.7": ["draughty"], "7.0 10.6 11.6": ["masturbatory"], "2.5 12.1 4.5": ["shrewder"], "3.9 3.6 7.1": ["retrievals"], "1.7 1.5 16.1": ["cardroom"], "-0.3 9.3 25.7": ["appetisers"], "1.8 12.8 -0.5": ["knowns"], "1.1 7.3 12.2": ["ureter"], "3.5 12.7 20.2": ["foxhunting"], "2.5 6.2 6.9": ["seedier"], "-1.4 8.8 2.3": ["havebeen"], "4.7 19.7 8.0": ["denialism"], "16.9 7.8 8.9": ["moonshot"], "-1.4 18.7 3.2": ["secularity"], "10.8 14.0 35.8": ["forkful"], "12.9 5.5 3.6": ["typifying"], "-1.9 6.6 19.2": ["fledge"], "1.1 14.8 0.1": ["overemphasizing"], "-14.9 3.3 8.1": ["intersession"], "6.6 7.3 25.2": ["dosas"], "-0.6 13.8 3.5": ["uprightness"], "5.2 6.5 5.0": ["jsut"], "-2.0 -5.6 1.3": ["thrombotic"], "-2.6 12.9 3.4": ["immoderate"], "7.2 -0.8 6.4": ["smartened"], "-3.7 5.6 11.9": ["mv"], "0.9 14.3 10.3": ["insensible"], "7.2 6.8 1.5": ["abashed"], "5.9 13.8 2.2": ["blowed"], "-0.5 8.9 7.6": ["hotfixes"], "-13.1 9.8 8.8": ["chemotherapeutics"], "5.1 1.5 4.2": ["motorcross"], "-2.1 7.5 7.9": ["remixer"], "2.4 6.1 32.4": ["beachcombing"], "4.5 7.3 8.0": ["onramps"], "2.6 3.1 5.1": ["reinventions"], "4.0 8.1 7.4": ["outmuscling"], "1.7 1.3 10.1": ["arizona"], "-0.3 3.7 2.4": ["overdubbed"], "6.3 6.0 5.0": ["nanocrystal"], "0.6 13.2 8.3": ["ronaldo"], "-1.7 13.3 -2.6": ["rescan"], "1.6 9.8 3.6": ["experimentalism"], "11.6 9.9 12.5": ["chupacabra"], "4.1 5.5 34.6": ["tagine"], "1.4 9.0 6.7": ["flytipping"], "3.6 21.1 11.9": ["polarizer"], "15.5 16.2 8.3": ["wireframe"], "6.4 10.8 4.8": ["overoptimistic"], "6.9 3.5 14.5": ["garnets"], "-6.2 4.6 8.5": ["vibraphonist"], "8.6 20.9 20.2": ["shogun"], "6.5 1.4 0.6": ["iseemedia"], "-0.6 6.1 1.4": ["televoting"], "4.9 31.3 -1.7": ["sapper"], "5.9 10.8 25.4": ["guido"], "-0.3 2.9 14.2": ["akong"], "7.6 4.0 9.2": ["sullies"], "8.7 10.7 10.3": ["kos"], "-10.0 7.1 8.8": ["overcollateralization"], "3.8 4.4 15.1": ["ruffed"], "16.2 21.9 15.0": ["infests"], "1.7 13.4 -5.7": ["emancipating"], "-0.8 7.1 -1.8": ["overplays"], "-1.4 2.0 -1.1": ["microturbines"], "3.7 34.2 11.0": ["wargame"], "1.1 11.7 9.4": ["perigee"], "-2.7 12.8 6.9": ["samadhi"], "21.7 12.0 16.8": ["frisbees"], "11.3 16.0 9.6": ["copse"], "4.5 -1.0 20.4": ["cockatiels"], "6.5 5.2 13.1": ["preciously"], "11.4 9.7 7.3": ["wantaway"], "-1.8 1.2 10.3": ["rundowns"], "5.1 11.4 5.6": ["celebrators"], "4.9 9.6 7.1": ["gracefulness"], "7.6 1.0 0.8": ["airtel"], "-4.1 0.2 -0.4": ["booksigning"], "2.7 9.4 13.3": ["irrigator"], "8.5 5.4 8.9": ["burble"], "16.9 11.9 6.9": ["livingroom"], "21.0 20.6 10.1": ["handmaidens"], "4.5 2.5 21.0": ["spreadable"], "-5.1 3.2 17.6": ["dewatered"], "4.8 1.4 11.3": ["lido"], "0.8 -0.0 4.3": ["sharecropping"], "1.7 -0.5 18.7": ["brocades"], "16.1 2.6 8.9": ["pirouetted"], "5.5 24.9 -0.2": ["oppostion"], "8.2 25.4 10.3": ["muggle"], "11.4 12.5 10.9": ["dimmest"], "1.9 -1.9 8.5": ["blogspot"], "15.9 8.4 12.0": ["entomb"], "0.8 8.4 3.0": ["arthralgia"], "-2.8 5.5 -0.5": ["bradycardia"], "3.9 4.4 7.1": ["metallurgists"], "10.0 4.6 8.1": ["narrowcasting"], "12.4 12.3 6.9": ["visages"], "7.6 -0.2 16.2": ["tasseled"], "16.2 8.6 9.3": ["touchpads"], "-0.6 6.2 17.1": ["figuration", "wu"], "-5.3 7.2 12.3": ["chanceless"], "5.7 1.0 1.6": ["slimness"], "-5.9 5.9 2.1": ["upskill"], "1.5 11.6 2.6": ["tourer"], "-5.3 1.8 14.6": ["woodstoves"], "8.2 23.3 3.5": ["bloodcurdling"], "17.2 5.8 11.5": ["hugh"], "4.2 8.7 0.1": ["pimavanserin"], "-0.9 4.0 2.7": ["naloxone"], "4.1 9.8 1.4": ["oversimplifies"], "3.1 -2.2 -0.9": ["verifier"], "10.5 27.1 15.7": ["phaser"], "3.1 5.0 17.2": ["daiquiris"], "9.1 -2.0 4.1": ["rerating"], "17.0 12.5 9.6": ["witchdoctor"], "-1.2 9.4 7.2": ["xxi"], "6.7 -1.0 16.1": ["loansharking"], "-0.4 -11.1 10.6": ["reopenings"], "10.3 8.2 8.8": ["munificence"], "-2.7 14.5 9.5": ["kayfabe"], "-2.5 6.7 8.3": ["chukka"], "-2.3 9.7 11.3": ["glibness"], "2.1 7.2 27.1": ["shorefront"], "9.3 4.5 5.9": ["preannouncement"], "-2.6 7.7 5.4": ["toileting"], "2.0 1.5 4.7": ["collaboratives"], "3.5 4.8 10.3": ["tricep"], "1.5 0.5 10.6": ["procuratorate"], "-5.5 9.1 12.4": ["marrieds"], "3.5 0.0 6.5": ["funked"], "1.7 10.0 4.3": ["speedometers"], "-0.5 1.9 10.4": ["boxset"], "5.1 10.0 21.9": ["fynbos"], "3.2 12.5 9.8": ["eviscerates"], "10.5 35.8 11.0": ["colonizer"], "1.3 6.3 4.2": ["unlinked"], "10.3 1.0 4.4": ["bops"], "20.6 0.0 13.6": ["unicycles"], "-1.5 -0.2 -0.4": ["vigabatrin"], "10.9 5.7 13.3": ["friezes"], "4.2 12.9 2.0": ["incurious"], "0.9 13.7 5.8": ["sadhu"], "5.9 10.8 18.8": ["clearcutting"], "2.0 12.9 38.2": ["fugu"], "-0.0 4.6 11.6": ["benchings"], "-2.6 6.3 5.6": ["recompile"], "18.6 2.7 14.4": ["jiggles"], "4.6 13.7 12.8": ["misplaying"], "-1.7 19.9 2.4": ["loadmaster"], "-3.6 4.2 3.6": ["novitiate"], "10.1 3.2 12.2": ["geomatics"], "7.0 22.2 5.2": ["dogcatcher"], "-4.2 10.2 16.7": ["schneid"], "6.9 2.3 7.9": ["bluestones"], "0.9 17.2 9.7": ["misalignments"], "2.3 4.4 4.8": ["whois"], "13.5 12.4 9.9": ["sieves"], "8.0 11.4 13.0": ["sqkm"], "6.8 16.2 6.1": ["inquisitions"], "1.9 8.1 23.5": ["citron"], "2.2 -1.9 17.4": ["plait"], "6.0 8.5 26.0": ["charbroiled"], "15.2 9.4 3.4": ["garishly"], "-3.1 15.0 5.1": ["histoplasmosis"], "-9.8 12.4 9.6": ["rimantadine"], "7.1 8.0 30.0": ["vegies"], "-6.2 22.7 -0.4": ["anticommunist"], "10.6 7.6 3.2": ["thisclose"], "-0.5 12.7 -1.3": ["realties"], "-2.6 18.0 7.6": ["filmgoer"], "9.7 7.0 41.1": ["yuzu"], "13.2 15.1 4.2": ["excreting"], "-3.2 0.7 20.9": ["noncertified"], "14.8 16.1 24.4": ["jigger"], "16.9 13.9 11.0": ["monorails"], "5.3 15.4 34.3": ["nasturtiums"], "11.6 0.1 12.6": ["cheapie"], "5.2 17.2 22.2": ["waterspouts"], "-3.3 13.1 -1.1": ["greatful"], "7.7 3.3 7.3": ["biochips"], "3.0 10.1 34.0": ["granita"], "0.6 13.4 0.6": ["bargainer"], "2.1 17.8 6.9": ["inconceivably"], "-4.8 16.2 11.9": ["eschatological"], "1.5 2.3 8.6": ["overspends"], "1.4 4.1 7.8": ["lululemon"], "10.4 -0.0 5.3": ["ebusiness"], "15.2 4.7 9.2": ["tepees"], "-1.0 7.9 8.2": ["diamondiferous", "sug"], "8.2 8.6 14.3": ["wuz"], "-5.1 6.3 5.0": ["keyboardists"], "-8.0 1.9 7.9": ["dramaturge"], "-2.3 9.7 4.2": ["amoung"], "4.5 11.8 17.1": ["hutong"], "4.8 6.4 19.9": ["kaka"], "-0.2 5.9 -3.3": ["rectifies"], "2.6 4.4 30.8": ["bao"], "7.9 14.2 2.2": ["unsurpassable"], "15.7 10.9 18.7": ["carnies"], "3.3 5.4 17.4": ["init"], "6.2 15.3 12.4": ["sorrowfully"], "1.4 8.5 2.0": ["systematized"], "7.6 6.3 1.0": ["cheif"], "4.1 20.9 1.0": ["unendurable"], "7.8 18.4 13.8": ["foible"], "7.2 17.9 -3.5": ["bluntest"], "5.0 8.6 17.8": ["sixteenths"], "-1.7 13.2 9.6": ["viewshed"], "8.6 4.1 9.3": ["pantaloons"], "-4.1 5.7 6.7": ["unsubscribed"], "1.2 5.0 5.7": ["laddish"], "-2.3 7.5 11.2": ["hyperpigmentation"], "3.0 6.7 10.6": ["windrows"], "6.4 12.4 12.4": ["companionable"], "0.8 9.9 7.5": ["amino"], "1.8 11.1 -3.9": ["ranter"], "11.5 3.4 10.2": ["choppier"], "9.9 9.1 21.7": ["mastiffs"], "4.3 20.4 2.4": ["nutjobs"], "1.6 9.3 5.9": ["fonder"], "3.5 7.4 0.7": ["countrywomen"], "-4.4 4.5 19.9": ["rebuys"], "-2.0 18.5 2.7": ["railhead"], "0.8 -7.7 12.2": ["superfine"], "15.0 15.1 0.3": ["thunderously"], "-2.5 4.0 3.6": ["maisonette"], "5.9 2.3 5.7": ["joyrides"], "6.0 6.1 0.2": ["warrantee"], "1.4 6.3 5.1": ["sich"], "6.0 6.5 6.6": ["nepotistic"], "5.0 11.4 9.3": ["blankie"], "1.9 5.1 9.6": ["fastback"], "-2.8 2.4 -0.0": ["epileptics"], "2.5 12.7 7.7": ["rendezvoused"], "-5.9 3.8 11.2": ["agroforestry"], "2.5 14.0 12.5": ["mediocrities"], "15.7 5.3 3.2": ["smashup"], "7.6 13.8 7.3": ["dancefloors"], "9.7 3.3 17.7": ["flouncy"], "-0.8 0.5 24.9": ["longboards"], "13.7 7.3 2.3": ["unhip"], "-0.6 8.9 -3.5": ["webzine"], "5.3 10.9 3.4": ["astrobiologist"], "-6.9 12.0 -0.4": ["literalist"], "11.1 8.2 11.3": ["heraldic"], "13.1 -1.6 -1.7": ["idents"], "10.2 2.1 14.4": ["reticulated"], "2.2 11.6 2.1": ["nonpartisanship"], "-2.0 3.9 6.6": ["backorder"], "-5.6 5.9 3.4": ["upregulated"], "-0.1 15.9 22.6": ["falconers"], "-0.5 12.0 10.9": ["epaulettes"], "4.7 11.3 13.4": ["reapportion"], "13.0 9.0 56.1": ["terrapin"], "1.2 15.0 4.9": ["felicity"], "10.9 20.5 24.2": ["cuckoos"], "-6.4 9.1 3.4": ["hydrocortisone"], "13.4 1.7 4.5": ["boomtowns"], "2.6 0.8 8.5": ["unconference"], "-3.8 10.6 1.5": ["outpour"], "2.0 6.8 12.8": ["bjs", "ither"], "2.6 -1.1 3.0": ["mem"], "-8.1 14.5 10.0": ["giftedness"], "3.1 7.0 14.6": ["telnet"], "9.8 13.6 15.1": ["attractor"], "16.9 7.0 13.9": ["pogo"], "9.5 19.6 4.5": ["polytheism"], "5.6 10.2 12.6": ["magmatic"], "-6.7 5.2 0.1": ["lthough"], "-0.5 11.2 5.3": ["unselfconscious"], "-1.6 1.7 9.7": ["errata"], "1.2 16.5 4.1": ["domestique"], "-4.7 -0.0 11.2": ["concelebrated"], "10.6 2.7 21.8": ["carob"], "2.9 11.3 2.4": ["reponsible"], "-0.6 9.7 5.2": ["undercounts"], "7.2 15.8 23.9": ["darlin"], "12.8 -3.5 -10.4": ["ots"], "-0.3 19.0 8.5": ["unloving"], "6.2 13.0 22.2": ["snorkels"], "11.4 10.5 5.8": ["handbill"], "1.4 4.9 10.8": ["dhabas"], "4.5 10.8 3.4": ["apposed"], "-0.1 0.3 -2.3": ["sidetracking"], "6.4 8.4 2.9": ["delinking"], "-1.0 0.2 9.8": ["yoa"], "-1.3 7.3 1.7": ["decompressed"], "-7.2 12.9 4.1": ["deplaning"], "4.3 5.6 9.7": ["micrometeorites"], "12.2 15.1 16.0": ["mano"], "2.1 8.6 3.3": ["ferromagnetic"], "7.2 7.0 7.5": ["mopes"], "12.6 5.6 7.8": ["overstimulated"], "4.3 1.8 -1.8": ["comme"], "-5.9 1.8 4.6": ["disinterment"], "6.1 13.2 5.6": ["befuddles"], "-1.2 4.3 12.3": ["antigraft"], "9.9 2.9 7.2": ["bioengineer"], "3.4 9.2 31.7": ["silkworm"], "3.4 5.3 22.0": ["fruited"], "4.3 15.3 14.1": ["pushup"], "5.7 -3.2 0.2": ["drycleaning"], "3.2 9.4 38.7": ["squab"], "-7.9 0.1 10.4": ["frontloading"], "7.8 18.3 4.1": ["superfans"], "-3.4 3.0 7.4": ["maurices"], "10.1 4.7 -2.7": ["legendry"], "0.2 9.2 -1.4": ["insufficiencies"], "12.5 5.6 7.1": ["portmanteau"], "0.0 10.8 -3.7": ["subheading"], "10.8 13.9 4.1": ["cozily"], "5.4 -3.0 12.4": ["coifed"], "10.2 15.2 10.9": ["groggily"], "4.2 5.7 8.1": ["misidentifying"], "16.9 16.9 9.9": ["stonewalls"], "6.8 5.6 17.8": ["wassail"], "8.4 4.0 10.7": ["fobs"], "6.2 2.9 4.5": ["sanitaryware"], "14.6 13.6 21.1": ["parasitism"], "1.4 12.0 19.7": ["muffs"], "-2.5 5.4 6.2": ["standpipes"], "9.5 31.4 5.6": ["crosshair"], "-6.4 2.8 2.7": ["bivalirudin"], "3.6 10.9 6.1": ["stakeouts"], "-2.2 3.8 3.4": ["unlistenable"], "9.3 6.2 13.7": ["icemaker"], "9.4 -3.6 -0.1": ["baulking"], "17.5 17.5 6.6": ["whirlwinds"], "4.1 11.4 12.0": ["catholics"], "10.1 15.5 5.7": ["imperishable"], "16.5 10.3 6.0": ["ook"], "-7.6 8.9 10.8": ["brut"], "13.3 10.2 13.5": ["shat"], "-1.8 24.1 6.3": ["defoliants"], "9.7 -0.3 12.4": ["rosin"], "3.9 5.8 6.6": ["etailers"], "-1.9 6.2 6.8": ["powerloom"], "8.3 12.3 6.9": ["jinxes"], "-2.9 11.5 7.6": ["misperceived"], "16.4 20.8 -2.7": ["snoopers"], "11.2 23.7 18.7": ["noob"], "5.6 6.4 9.3": ["aarti"], "-0.4 7.9 4.4": ["supermom"], "7.5 7.9 -0.4": ["reacquisition"], "-7.1 15.3 6.5": ["unexpressed"], "9.4 5.0 3.7": ["befitted"], "5.7 -1.6 19.4": ["yee"], "-5.5 1.4 5.7": ["abatacept"], "-8.9 10.9 6.8": ["midgrade"], "13.1 3.8 8.8": ["spiffing"], "6.3 10.3 5.8": ["catalysing"], "-2.5 8.4 5.1": ["dissatisfying"], "-7.1 6.6 7.0": ["nonparty"], "7.2 7.0 -4.2": ["unparalled"], "-9.7 10.7 4.8": ["generalizable"], "16.4 11.3 8.0": ["mousepad"], "-1.0 -6.9 10.0": ["dietetic"], "-3.4 16.4 9.6": ["geocaches"], "-0.3 16.0 0.8": ["photographically"], "12.3 2.8 -6.5": ["conceptualising"], "5.3 11.9 1.6": ["hectored"], "-0.7 11.2 6.5": ["surrealists"], "13.8 27.2 20.2": ["slavers"], "-0.9 -2.1 5.2": ["traineeships"], "10.3 16.9 10.5": ["citronella"], "-16.3 16.2 0.9": ["reenlisted"], "-6.7 5.1 11.3": ["allogeneic", "nonimmigrant"], "12.1 9.6 14.6": ["droops"], "-3.3 5.6 7.4": ["asphalted"], "8.6 13.9 5.7": ["shamble"], "14.9 5.8 13.7": ["hutches"], "-4.2 3.4 11.9": ["sangeet"], "12.8 43.9 7.1": ["antiaircraft"], "17.5 20.1 31.5": ["fantail"], "17.7 4.6 8.1": ["psuedo"], "16.5 11.3 17.9": ["strangler"], "-2.5 10.9 -6.6": ["strenghten"], "13.1 7.6 15.0": ["sidles"], "3.9 12.2 12.2": ["ripest"], "14.9 33.3 11.3": ["missle"], "5.5 8.6 32.8": ["scrapple"], "4.0 2.2 -5.5": ["isthe"], "-10.3 4.4 6.4": ["stepfamily"], "-9.5 4.5 4.8": ["kirtan"], "10.2 10.5 11.7": ["boppers"], "-1.1 10.4 21.0": ["locavores"], "-6.1 11.8 -2.8": ["sociologically"], "10.0 9.4 10.2": ["crick"], "-6.0 6.6 9.2": ["overcorrect"], "15.5 9.5 5.4": ["motherlode"], "3.4 6.4 20.3": ["thai"], "-2.9 7.6 11.5": ["connoisseurship"], "17.0 5.7 1.0": ["supercharging"], "14.3 10.4 11.9": ["croupier"], "0.2 6.0 9.7": ["airiness"], "10.7 11.6 7.8": ["transmutation"], "-6.7 12.4 1.5": ["exigent"], "4.4 -5.5 6.8": ["rhapsodized"], "3.1 17.1 11.3": ["depravation"], "11.6 7.5 -0.7": ["externalization"], "7.9 9.2 -1.4": ["indemnifying"], "4.0 12.6 5.7": ["boyz"], "6.5 8.2 16.3": ["goiter"], "3.7 3.0 11.1": ["greaser"], "13.5 22.8 7.7": ["neocolonialism"], "1.2 9.8 17.8": ["chametz"], "9.2 8.7 6.8": ["sheikdoms"], "6.0 14.2 6.4": ["blinatumomab"], "0.5 -0.5 2.6": ["outhomered"], "-6.5 13.4 8.8": ["vaccinia"], "1.5 9.1 -2.3": ["contentiously"], "1.3 17.1 10.2": ["addons"], "10.6 14.4 11.4": ["derelicts"], "13.4 22.0 5.4": ["gunslinging"], "9.1 9.4 8.1": ["technophile"], "0.2 -1.1 16.8": ["offertory"], "4.0 7.3 7.4": ["schoolbag"], "-4.0 26.0 8.9": ["aloneness"], "15.7 4.5 6.3": ["stks"], "1.7 6.7 -3.9": ["motorcars"], "6.1 21.3 3.1": ["dualistic"], "14.3 17.3 19.3": ["harpy"], "-4.0 7.7 6.0": ["unrestored"], "-5.6 7.9 10.7": ["facultative"], "-4.3 1.6 7.8": ["winterization"], "13.1 17.3 10.7": ["upsmanship"], "7.3 4.5 12.0": ["mistyped"], "15.7 9.7 24.2": ["catsup"], "7.7 4.4 0.6": ["siezed"], "12.7 3.9 11.7": ["grottos"], "5.7 4.1 12.5": ["headends"], "16.2 0.8 2.2": ["streetlamps"], "1.6 9.7 -4.2": ["dishonouring"], "1.9 6.7 2.1": ["transiently"], "14.9 1.3 1.8": ["vroom"], "13.3 8.6 22.7": ["whorls"], "-9.1 7.5 4.1": ["linezolid"], "5.4 2.4 -0.6": ["ultracompact"], "7.1 1.9 10.9": ["infographics"], "3.8 17.0 12.2": ["tessellation"], "4.6 1.9 32.5": ["tzatziki"], "15.9 9.6 7.0": ["antimonopoly"], "2.8 9.6 -0.3": ["protegee"], "5.0 3.6 2.1": ["pula"], "-2.5 23.4 3.0": ["atropine"], "6.3 3.8 9.8": ["goofier"], "-2.7 25.5 7.5": ["ethnocentrism"], "12.3 10.3 5.4": ["stencilled"], "1.4 3.7 3.4": ["suport"], "-0.1 4.9 2.3": ["amens"], "13.5 5.8 9.6": ["gers"], "12.0 9.1 12.9": ["noggins"], "10.0 8.2 52.1": ["tunas"], "3.0 7.4 5.3": ["facia"], "8.9 7.9 6.1": ["agric"], "7.4 -0.7 7.9": ["switchyard"], "-2.6 13.0 10.4": ["desiccation"], "10.4 6.4 5.2": ["tittering"], "6.8 5.3 10.5": ["cager"], "1.6 8.8 12.7": ["wristy"], "17.6 5.6 14.6": ["bigfoot"], "1.5 4.3 3.4": ["mannitol"], "10.0 14.6 2.0": ["jukes"], "-3.1 8.4 13.0": ["hikoi"], "23.8 1.7 -3.2": ["whitegoods"], "5.0 19.8 6.6": ["clenches"], "1.5 7.8 2.6": ["lossy"], "5.1 13.1 -0.7": ["inundates"], "-1.1 -1.6 8.8": ["mscmd"], "3.0 -1.8 8.7": ["potboilers"], "1.0 16.4 11.8": ["physicalness"], "-6.4 10.2 14.1": ["screentime"], "4.6 8.8 -1.4": ["nach"], "5.1 10.3 4.9": ["conjunctions"], "1.0 5.0 4.0": ["hammam"], "12.7 12.0 26.4": ["pupa"], "9.6 18.2 4.1": ["programed"], "2.0 19.8 10.8": ["wildernesses"], "11.2 17.1 13.1": ["mauler"], "5.7 11.8 21.2": ["biota"], "-2.3 12.7 2.6": ["unconditioned"], "-0.9 7.6 12.5": ["potteries"], "1.2 0.8 16.2": ["linseed"], "2.4 3.4 -0.6": ["maintainance"], "7.5 8.4 19.7": ["pedalo"], "20.2 20.6 11.4": ["vikings"], "3.5 5.7 4.3": ["anacetrapib"], "-2.7 9.0 4.7": ["sufi"], "-8.9 1.3 0.6": ["hyperuricemia"], "12.8 6.4 1.9": ["steamrolls"], "1.1 14.5 6.9": ["signalman"], "18.6 19.8 18.6": ["voyager"], "2.3 19.1 21.1": ["knapweed"], "5.6 9.2 3.6": ["greyscale"], "-2.0 3.2 11.5": ["madrigals"], "5.2 1.8 11.3": ["prenuptial"], "-6.5 2.2 -3.3": ["unproduced"], "5.7 10.0 14.6": ["tweeps"], "11.7 2.9 9.4": ["illinois"], "4.1 5.0 12.0": ["horsebox"], "9.6 4.1 8.6": ["toots"], "4.8 28.0 3.8": ["repulsing"], "12.2 11.7 13.0": ["galactico"], "11.8 17.7 5.7": ["puritanism"], "-4.2 9.9 10.1": ["homesters"], "17.8 1.7 5.3": ["preannounced"], "-2.1 4.2 -1.7": ["denufosol"], "3.7 9.9 12.7": ["grazier"], "-1.4 9.4 8.1": ["meticulousness"], "13.9 3.1 4.8": ["sashays"], "-4.2 11.7 2.3": ["kinesthetic"], "-5.9 5.2 16.4": ["redelivery"], "-2.9 0.9 3.3": ["hexane"], "-1.7 2.8 9.9": ["karters"], "-7.1 17.1 2.0": ["inculcation"], "16.6 24.2 20.0": ["frogmen"], "4.4 8.2 10.4": ["spline"], "-6.0 9.8 1.9": ["talaq"], "3.8 38.3 5.4": ["betrayers"], "12.9 -0.7 7.9": ["gyrates"], "-2.5 14.4 17.9": ["antitax"], "-5.2 14.6 9.2": ["coachspeak"], "4.2 5.6 8.9": ["midriffs"], "2.6 12.0 12.5": ["tradewinds"], "-3.1 2.0 8.4": ["accreditors"], "-9.4 10.7 8.0": ["narratively"], "0.7 4.5 18.5": ["littles"], "17.3 10.9 12.7": ["turreted"], "-0.9 12.5 5.8": ["eyedrops"], "3.8 5.4 11.0": ["crosscutting"], "16.6 21.5 3.9": ["transfigured"], "2.6 8.2 12.3": ["sprits"], "1.2 24.4 -2.5": ["underequipped"], "3.5 3.4 6.2": ["refractories"], "2.2 1.8 17.7": ["felting"], "-3.9 1.8 14.5": ["fumigants"], "4.1 8.4 3.0": ["reloadable"], "3.8 8.8 14.1": ["begetting"], "10.8 3.7 -3.5": ["playpens"], "-3.3 14.0 -2.5": ["tittle"], "13.7 6.8 12.7": ["ironworks"], "9.3 11.4 9.4": ["disentangling"], "3.3 11.0 6.7": ["sider"], "10.1 10.3 19.3": ["gooseneck"], "8.8 10.9 2.1": ["unhelpfully"], "17.7 7.9 6.9": ["gawp"], "8.5 11.0 5.6": ["prevaricating"], "15.2 5.9 13.8": ["hooters"], "17.3 4.7 1.9": ["graffitied"], "9.8 3.9 8.1": ["joo", "truncates"], "13.3 8.6 16.4": ["rangoli"], "6.9 25.9 2.7": ["inhumanly"], "-6.6 22.4 9.8": ["enumerator"], "1.8 2.7 4.5": ["dutasteride"], "7.8 6.5 14.2": ["greg"], "-1.4 7.7 11.2": ["flowback"], "2.4 23.8 5.2": ["hearers"], "-1.5 11.1 9.0": ["nonvoters"], "12.3 17.4 30.6": ["jiggers"], "28.9 -1.8 1.2": ["lossmaking"], "-5.5 -1.7 7.2": ["multiprotocol"], "7.7 -2.9 24.6": ["chippies"], "1.9 -3.6 1.8": ["footbal"], "17.9 7.1 -1.8": ["advertisment"], "18.0 2.8 3.6": ["megadeals"], "11.9 14.1 9.5": ["deigns"], "-4.1 10.4 5.3": ["maced"], "11.4 6.9 14.5": ["delectation"], "-5.0 4.7 10.9": ["immunoglobulins"], "6.2 8.2 10.7": ["steppin"], "-9.6 1.0 14.4": ["gewog"], "20.3 10.1 12.5": ["temptingly"], "7.9 2.8 4.9": ["foregoes"], "9.6 9.4 6.6": ["dethrones"], "-11.4 8.2 5.4": ["colposcopy"], "11.7 7.1 11.2": ["shrivels"], "2.6 14.0 7.8": ["zags"], "13.5 6.7 7.3": ["biomimetic"], "5.7 13.7 11.5": ["psychobilly"], "5.1 5.1 14.8": ["loc"], "6.6 5.6 18.1": ["budgies"], "-3.7 0.0 15.7": ["unpackaged"], "7.0 7.3 11.9": ["rubbings"], "1.8 -0.2 4.8": ["isoform"], "5.5 8.7 13.1": ["trunked"], "16.4 6.7 14.5": ["holey"], "2.4 10.5 32.9": ["barbel"], "-9.8 5.0 9.5": ["bloodwork"], "13.8 0.4 21.6": ["finial"], "1.5 7.3 10.3": ["moll"], "11.9 1.0 10.1": ["popster"], "14.6 17.7 11.3": ["fornicating"], "6.6 6.1 0.2": ["swot"], "12.9 16.8 8.4": ["glowered"], "9.0 6.4 2.9": ["popstars"], "9.2 0.4 16.3": ["twined"], "-17.2 21.4 7.6": ["reenlist"], "0.5 20.8 17.8": ["armyworms"], "7.0 -0.4 17.4": ["tbs"], "11.1 2.2 5.1": ["compounder"], "4.4 2.0 12.1": ["handcrafting"], "-12.3 8.8 7.7": ["preceptor"], "4.6 -0.4 9.3": ["flounce"], "5.5 10.6 16.7": ["hittin"], "8.0 3.9 -2.9": ["derivates"], "-11.2 1.2 0.1": ["clientless"], "4.0 7.4 8.6": ["throughly"], "6.9 5.9 10.1": ["henry"], "1.6 -1.1 4.7": ["hallmarked"], "15.6 6.3 9.6": ["thimbles"], "-0.9 -9.6 12.6": ["serigraphs"], "-5.4 8.3 12.3": ["nondrinkers"], "-7.0 0.2 9.2": ["phrasings"], "3.5 6.7 15.8": ["betweens"], "10.7 14.5 11.4": ["ringpost"], "8.0 2.6 3.3": ["brandname"], "2.5 16.4 6.2": ["secularisation"], "-7.5 6.9 0.7": ["formulator"], "13.3 11.4 32.8": ["mayfly"], "11.3 5.2 12.3": ["balsa"], "-2.1 -5.4 -0.7": ["productized"], "-1.5 4.3 3.4": ["photochemical"], "15.0 18.3 30.4": ["beaked"], "4.2 7.7 5.6": ["transliterated"], "18.6 14.8 6.7": ["aeons"], "6.1 2.0 -1.0": ["prestigous"], "7.6 -0.1 35.9": ["truffled"], "0.5 11.3 4.9": ["overstaffing"], "10.4 2.4 14.1": ["uno"], "-4.5 9.1 9.0": ["kettling"], "6.9 -0.5 14.4": ["crankshafts"], "10.3 26.2 9.8": ["irreverently"], "6.7 1.9 11.8": ["irrepressibly"], "9.1 2.0 15.9": ["restauranteur"], "0.1 -3.3 16.9": ["fascinators"], "-4.3 1.6 9.1": ["torah"], "8.4 9.3 0.0": ["smouldered"], "-0.2 6.3 -2.1": ["diskette"], "-2.3 11.1 10.3": ["chappals"], "0.7 3.8 14.8": ["summering"], "-4.4 2.8 3.2": ["disbar"], "3.6 9.8 10.7": ["unbutton"], "-0.6 7.1 5.7": ["cytoplasmic"], "6.1 10.7 16.5": ["rippers"], "1.1 -1.6 4.0": ["realestate"], "8.3 16.2 15.8": ["skywatchers"], "1.7 4.5 34.9": ["dace"], "5.4 13.4 13.1": ["submerges"], "-12.6 15.2 6.4": ["likeliness"], "4.7 2.3 4.8": ["antidoping"], "11.6 4.6 3.3": ["reincorporated"], "12.6 11.9 1.4": ["unboxed"], "3.0 17.9 7.6": ["dialectics"], "-6.8 13.0 -1.9": ["madrassah"], "-1.4 26.0 8.8": ["battlegroup"], "-4.1 2.5 -1.2": ["humidification"], "12.8 11.8 36.4": ["cephalopods"], "-0.4 2.1 9.8": ["harpists"], "-4.8 4.8 5.7": ["rightback"], "8.8 9.7 13.9": ["peewees"], "-0.9 -5.7 7.2": ["perscription"], "-0.7 3.7 3.3": ["postmortems"], "13.4 11.5 35.0": ["copepods"], "-0.6 2.5 1.2": ["plagiarising"], "9.7 9.1 5.1": ["bashfully"], "4.4 7.8 -6.2": ["evincing"], "-4.1 2.7 -4.3": ["felicitating"], "9.7 6.7 4.2": ["mussed"], "1.0 -0.3 9.5": ["yar"], "20.1 14.8 11.0": ["smasher"], "-4.1 11.8 8.0": ["inactivates"], "11.7 14.1 -0.2": ["omnidirectional"], "15.1 7.3 19.7": ["lusciously"], "8.4 2.3 1.3": ["ust"], "8.3 13.1 6.4": ["matchboxes"], "3.7 5.0 21.9": ["multigrain"], "20.1 13.0 0.8": ["hoaxers"], "1.5 -3.9 14.4": ["romper"], "9.7 16.5 14.2": ["maroons"], "-4.1 18.9 0.5": ["triaging"], "-3.3 12.0 9.8": ["medicinally"], "1.0 8.4 0.2": ["bonafides"], "-1.5 -2.2 6.6": ["punchier"], "9.0 6.9 6.7": ["savannahs"], "5.4 8.9 9.0": ["duffel"], "-1.8 11.0 16.1": ["stickwork"], "15.0 11.4 11.5": ["earthmover"], "10.1 9.0 28.5": ["trillium"], "-0.9 7.2 3.4": ["odorant"], "10.0 5.9 9.5": ["electropop"], "16.3 8.0 5.0": ["daubing"], "7.8 13.6 14.7": ["sally"], "-5.0 15.2 1.4": ["oncogenic"], "-2.4 4.2 31.2": ["fattier"], "5.1 3.8 -1.8": ["ecards"], "-11.6 12.9 6.6": ["decisional"], "15.9 3.9 5.2": ["stagecoaches"], "-0.6 20.7 14.0": ["crimefighting"], "5.4 8.2 3.9": ["decathletes"], "3.5 2.4 5.8": ["multifaith"], "-2.8 6.7 4.2": ["biliary"], "5.3 0.5 10.9": ["yeon"], "4.4 14.5 2.6": ["continously"], "6.4 6.0 3.0": ["footwell"], "-1.5 6.0 13.6": ["borings"], "20.4 -10.1 5.2": ["logoed"], "4.6 5.3 13.6": ["jamie"], "1.8 5.9 16.5": ["southcentral"], "8.1 8.4 15.3": ["charles"], "0.2 -0.7 4.1": ["starpower"], "3.1 3.2 13.7": ["dhol"], "9.8 12.1 14.3": ["pejoratively"], "-0.2 0.7 11.8": ["tibial"], "-1.1 10.5 7.2": ["guillotined"], "-2.6 17.7 11.7": ["rearguards"], "6.6 4.8 1.1": ["playbacks"], "1.6 3.3 -0.6": ["categorises"], "-2.3 5.7 9.1": ["bioactivity"], "-5.0 7.8 11.1": ["mir"], "3.4 -1.1 14.8": ["marketmen"], "2.5 9.9 9.2": ["ralliers"], "2.6 1.3 37.4": ["pomelo"], "-2.8 16.2 5.5": ["dissapointment"], "-1.6 -1.3 9.9": ["monotypes"], "5.5 15.9 7.7": ["symmetries"], "-2.3 6.3 6.9": ["driveshafts"], "8.5 25.0 2.0": ["cyberworld"], "2.0 1.4 3.1": ["mimetic"], "0.7 8.5 40.8": ["chubs"], "6.5 18.8 12.3": ["affably"], "9.1 6.7 2.6": ["yukking"], "-6.5 9.8 3.6": ["diarists"], "3.9 -2.5 9.9": ["sion"], "-0.1 11.3 8.2": ["draftniks"], "-0.2 5.1 -4.5": ["eld"], "-1.2 0.3 10.3": ["rompers"], "12.0 5.6 6.0": ["knockin"], "3.1 12.4 8.7": ["midmajor"], "0.5 -1.7 16.5": ["wholegrain"], "14.5 14.6 6.9": ["conk"], "-2.5 10.7 2.5": ["distressful"], "16.5 16.0 12.2": ["satyr"], "6.7 -3.0 20.1": ["bella"], "-3.3 13.8 8.6": ["sureness"], "4.6 21.1 6.1": ["impossibilities"], "2.9 5.7 9.0": ["hygienically"], "0.0 13.6 9.5": ["flagmen"], "-3.3 9.1 8.7": ["endocytosis"], "-9.2 10.5 -6.9": ["excepts"], "4.9 7.6 1.8": ["spiritedly"], "20.3 14.5 20.9": ["chomps"], "16.7 19.1 10.0": ["despoil"], "1.5 -3.7 1.6": ["msf"], "8.9 16.4 16.8": ["outcompete"], "5.9 -12.6 10.5": ["ture"], "20.1 -5.2 10.9": ["pigtailed"], "6.5 5.3 20.2": ["taverna"], "11.6 12.9 0.0": ["inquisitorial"], "15.6 7.2 20.0": ["chippers"], "-1.5 5.2 7.3": ["highweight"], "5.3 6.2 6.3": ["appalls"], "-2.3 20.9 11.4": ["proc"], "-4.1 8.5 1.0": ["integrationist"], "9.6 -1.3 11.3": ["hipped"], "-6.3 7.7 13.1": ["derogations"], "11.4 2.7 6.5": ["thelondonpaper"], "-4.9 4.6 1.5": ["deselected"], "11.6 7.4 5.2": ["reimagines"], "9.4 6.8 6.6": ["rooflines"], "11.9 14.1 17.5": ["fertilising"], "-10.8 2.5 -3.5": ["pulmonologists"], "4.1 6.0 5.0": ["unobjectionable"], "10.9 9.8 14.9": ["lemme"], "-1.8 2.5 4.7": ["rea"], "2.1 22.9 3.9": ["checkmated"], "2.8 -2.5 16.3": ["alginate"], "7.9 11.3 1.6": ["staunched"], "-3.8 4.2 4.4": ["keratoconus"], "8.4 11.4 12.9": ["downstage"], "0.3 4.2 34.6": ["fishponds"], "1.9 1.7 2.2": ["morcha"], "-1.4 17.4 11.2": ["maladaptive"], "-4.3 11.3 -0.1": ["unacceptability"], "3.4 11.4 5.4": ["nanodiamonds"], "13.6 26.6 8.4": ["jackboot"], "3.3 4.3 5.6": ["carbonatite"], "17.1 6.2 14.3": ["gurning"], "-3.9 10.4 15.1": ["stroma"], "10.5 3.5 7.5": ["magnifiers"], "-0.4 8.7 11.8": ["subcomponents"], "1.4 14.9 10.9": ["kraal"], "4.1 22.8 12.1": ["instinctually"], "3.1 4.0 18.2": ["blusher"], "-7.6 2.5 -4.4": ["belives"], "8.1 3.3 8.8": ["arrhythmic"], "2.5 16.8 10.2": ["prohibitionist"], "-7.5 17.8 4.9": ["centralist"], "13.8 9.7 4.4": ["deodorizer"], "5.4 3.2 8.9": ["stickered"], "7.8 5.2 9.3": ["gabby"], "4.8 0.1 5.8": ["mumblings"], "1.9 5.5 8.4": ["griot"], "14.3 9.6 9.5": ["canted"], "4.0 4.8 0.2": ["recommencing"], "13.4 4.8 21.8": ["straggly"], "-0.7 17.8 9.1": ["understatements"], "8.7 1.7 11.2": ["lisping"], "-5.7 10.3 1.7": ["discordance"], "14.4 17.0 7.7": ["errantly"], "-5.3 4.6 15.4": ["matings"], "-4.1 1.9 13.8": ["sorbent"], "6.5 13.4 40.5": ["hammerheads"], "2.8 11.4 12.5": ["guanxi"], "-2.4 15.6 5.1": ["damagingly"], "-7.3 0.6 9.7": ["nonprime"], "6.5 7.8 8.5": ["superfluid"], "2.6 10.7 7.4": ["sumps"], "-5.2 9.0 6.3": ["combinable"], "6.8 3.2 13.4": ["bok"], "7.4 12.0 7.7": ["wheedling"], "6.4 12.4 7.4": ["repower"], "-7.3 12.9 4.6": ["submenu"], "2.7 9.9 5.9": ["puzzlingly"], "1.4 5.2 7.5": ["nephropathy"], "0.3 2.6 10.7": ["jee"], "0.7 20.1 13.6": ["sinless"], "-9.5 12.1 1.8": ["lst"], "3.9 20.2 13.8": ["intractability"], "7.8 8.2 12.4": ["scram"], "-1.3 21.4 1.0": ["ahimsa"], "5.4 6.7 6.3": ["microcapsules"], "16.8 13.5 12.1": ["flummox"], "6.3 18.7 13.8": ["transposons"], "6.7 4.4 11.4": ["primp"], "1.2 4.0 6.6": ["tahsildar"], "4.3 -3.1 7.1": ["haircutting"], "5.5 6.1 13.0": ["snoozefest"], "-8.8 11.6 2.0": ["redesignation"], "8.4 10.5 11.8": ["lamer"], "9.6 8.5 11.3": ["graybeards"], "0.1 -0.8 5.5": ["expiries"], "-0.2 10.5 4.8": ["attainments"], "2.8 2.7 4.7": ["philately"], "9.2 11.5 4.9": ["babyish"], "-0.1 0.5 8.3": ["collab"], "-2.8 11.8 8.4": ["untutored"], "4.1 8.0 0.7": ["dendrimers"], "6.8 2.3 5.3": ["zoners"], "-1.0 9.3 8.2": ["scatback"], "23.5 12.3 16.4": ["hairballs"], "16.2 6.8 7.7": ["econo"], "16.9 6.2 5.3": ["tsars"], "22.2 17.2 7.3": ["upraised"], "3.7 -0.9 13.6": ["resealable"], "10.6 9.0 21.4": ["trilby"], "-0.6 5.6 1.4": ["cooktops"], "6.0 6.8 15.6": ["labradors"], "12.7 27.3 12.9": ["wusses"], "4.4 -5.9 1.8": ["frittered"], "13.4 14.2 20.9": ["megafauna"], "3.0 15.5 3.5": ["defendents"], "4.9 10.5 -0.7": ["appurtenances"], "4.2 12.7 11.1": ["stockworks"], "-8.8 15.9 7.2": ["exorcists"], "-6.0 21.4 11.6": ["amiability"], "11.4 3.7 7.2": ["workbenches"], "-13.5 6.4 4.2": ["terminable"], "-2.6 11.1 0.6": ["patdown"], "8.9 12.8 7.1": ["vertices"], "-0.0 13.3 10.4": ["mindfully", "railer"], "17.2 20.4 8.2": ["imps"], "-2.3 1.3 1.6": ["consistence"], "0.4 -0.2 36.8": ["boudin"], "8.3 11.1 10.1": ["massif"], "3.8 7.9 15.1": ["dag"], "14.5 11.9 5.3": ["eery"], "2.1 5.8 -6.8": ["overemphasised"], "15.2 26.4 18.5": ["uglies"], "2.3 7.8 8.8": ["suppositories"], "10.4 0.4 0.5": ["countersue"], "2.1 1.3 23.4": ["guavas"], "3.2 5.5 10.6": ["hospitalizing"], "4.4 16.6 7.0": ["steeliness"], "1.0 14.6 -2.3": ["embarass"], "6.1 8.9 10.4": ["waylay"], "12.2 14.2 8.6": ["gainst"], "-0.4 -6.2 1.3": ["lectureship"], "-0.5 1.4 16.9": ["unbleached"], "11.5 20.6 12.8": ["glyph"], "18.9 9.3 22.2": ["rhinoceroses"], "13.8 0.1 15.5": ["beery"], "13.8 12.5 10.5": ["truckie"], "-0.2 8.2 1.0": ["discoverability"], "-5.9 0.8 5.6": ["alchohol"], "7.1 -5.2 12.6": ["latenight"], "2.2 13.6 11.1": ["acculturated"], "1.8 10.0 9.5": ["cheerlead"], "-5.1 11.2 -2.6": ["condemnatory"], "-1.5 17.7 3.4": ["multipath"], "0.7 7.5 15.5": ["redeye"], "6.7 10.7 6.5": ["spanks"], "-1.8 12.6 3.8": ["undemocratically"], "5.5 6.8 7.7": ["denotification"], "7.2 5.3 -4.9": ["derecognition"], "-10.8 4.0 7.5": ["aldosterone"], "4.9 9.8 11.3": ["landfalls"], "16.1 7.1 15.3": ["deckchair"], "2.9 14.8 13.6": ["cheatin"], "-0.9 11.2 27.6": ["hellebores"], "-13.6 -0.7 -0.1": ["reoffended"], "5.4 16.6 6.3": ["scariness"], "8.0 2.3 16.6": ["kohl"], "-5.3 16.7 10.3": ["occultation"], "3.8 0.6 16.6": ["mocktails"], "5.2 27.8 3.4": ["cyberthreats"], "5.0 9.1 9.1": ["guideway"], "20.7 14.0 8.1": ["thrumming"], "0.9 16.9 11.6": ["gamertag"], "3.3 7.3 10.7": ["margined"], "14.7 12.7 17.0": ["yankee"], "0.0 14.2 8.2": ["gloominess"], "-2.5 20.3 4.6": ["casteist"], "6.9 8.3 7.3": ["nuvifone"], "-0.6 3.1 0.1": ["laxness"], "2.8 -3.4 2.4": ["additon"], "3.2 4.3 1.3": ["pk"], "14.2 6.7 4.2": ["prefigured"], "-5.5 10.4 12.4": ["chrysotile"], "10.5 3.9 13.2": ["rarin"], "3.0 -3.5 4.3": ["ortho"], "7.7 9.7 37.9": ["spanakopita"], "-13.0 -0.5 0.7": ["anticonvulsants"], "0.6 -4.8 2.0": ["diskettes"], "-9.5 7.9 20.3": ["cabernets"], "1.1 17.7 -1.4": ["abjure"], "9.7 18.8 10.6": ["whupping"], "1.6 9.7 9.5": ["spectate"], "-5.1 1.6 -5.5": ["ombudsperson"], "12.9 8.8 20.4": ["flakey", "cardinalis"], "5.0 5.8 4.0": ["worriedly"], "2.1 6.3 4.2": ["orexin"], "-2.1 11.9 2.5": ["burkha"], "9.3 -2.4 17.7": ["shiuan"], "15.5 7.6 12.2": ["forwarder"], "0.6 5.5 -2.9": ["memebers"], "14.0 22.2 17.2": ["blunderbuss"], "-2.4 19.0 4.6": ["federalizing"], "-3.8 10.4 10.1": ["backhauling"], "12.5 18.1 15.8": ["warthogs"], "-5.9 1.4 12.0": ["anak"], "3.6 18.9 9.8": ["aright"], "22.7 12.2 18.6": ["slingers"], "7.2 7.8 8.6": ["doji"], "-1.4 8.0 2.7": ["sportiest"], "-2.5 7.2 12.9": ["woh"], "2.9 8.1 3.0": ["naysaying", "fibrosing"], "8.0 4.4 7.0": ["dendrimer"], "1.9 12.3 0.4": ["reducible"], "4.0 28.9 15.8": ["pokemon"], "-11.3 4.6 5.9": ["woredas"], "-8.4 9.2 3.9": ["deselect"], "1.5 2.5 -1.2": ["cataloger"], "5.8 9.7 11.0": ["microstructures"], "-1.3 8.4 2.9": ["wifes"], "15.2 1.1 -3.0": ["limbered"], "9.9 5.8 8.0": ["haring"], "12.2 32.4 7.9": ["unmerciful"], "7.8 12.4 15.2": ["retrans"], "3.5 -0.3 3.0": ["spick"], "9.7 -1.6 3.7": ["lea"], "12.1 7.2 25.4": ["fixins"], "13.1 22.6 8.5": ["damnit"], "-3.3 16.1 1.9": ["overreactions"], "17.5 5.1 12.1": ["festoons"], "4.7 10.4 8.6": ["suffuses"], "4.3 3.5 11.3": ["jested"], "3.2 2.4 10.7": ["kilocalories"], "5.0 -1.1 6.0": ["fot"], "-2.5 -2.5 13.9": ["intercounty"], "17.5 30.2 3.0": ["slayers"], "-1.1 4.8 2.1": ["heliports"], "2.8 -0.7 34.6": ["tagliatelle"], "4.8 5.9 5.0": ["diskless"], "-2.6 10.8 2.8": ["professionalizing"], "-2.3 1.3 11.9": ["residentially"], "1.1 24.8 4.7": ["eavesdropper"], "0.0 9.6 12.8": ["nondestructive"], "-6.8 7.6 11.5": ["monounsaturated"], "12.5 8.2 24.9": ["springbok"], "3.3 7.7 2.8": ["hysteric"], "-0.8 12.6 10.3": ["hydrokinetic"], "2.6 0.3 2.3": ["dronedarone"], "4.6 17.3 0.5": ["cramdown"], "4.3 6.7 1.6": ["ballboys"], "-10.0 2.6 15.7": ["standardbreds"], "-6.1 25.0 9.9": ["supplementals"], "6.0 9.3 33.8": ["sambar"], "2.4 13.7 6.9": ["phonemes"], "4.6 2.5 23.5": ["kugel"], "12.8 7.0 12.3": ["sackful"], "-4.4 14.5 4.8": ["wali"], "13.6 -0.4 9.9": ["dubai"], "2.8 4.8 8.3": ["threequarter"], "-1.9 0.2 0.6": ["convoked"], "3.6 7.3 5.9": ["cognate"], "1.9 14.7 2.4": ["ablution"], "-1.5 5.5 9.9": ["prepreg"], "3.5 18.6 27.3": ["foredeck"], "13.3 10.0 9.4": ["barefaced"], "4.7 5.7 3.1": ["blogpost"], "8.9 -2.6 5.5": ["dur"], "9.7 1.1 14.9": ["clucked"], "-1.9 -8.9 9.5": ["noong"], "11.6 12.3 11.3": ["mucker"], "11.2 1.8 15.4": ["exotically"], "6.2 17.6 -1.2": ["subversively"], "-6.3 8.1 -1.1": ["externals"], "-5.8 0.5 0.4": ["concordant"], "13.7 4.0 9.2": ["frippery"], "-2.9 11.3 0.5": ["stereotactic"], "-3.3 11.4 5.1": ["irreversibility"], "16.7 8.4 16.0": ["gloaming"], "17.1 2.3 22.9": ["leavings"], "8.5 1.4 13.6": ["zealand"], "-4.3 5.2 10.0": ["peginterferon"], "6.3 10.6 21.5": ["seashores"], "-6.4 8.9 13.2": ["cyanidation"], "0.3 3.1 9.7": ["arb"], "6.3 14.6 6.6": ["roger"], "-0.0 -2.5 2.7": ["midpriced"], "21.4 0.6 7.8": ["xylophones"], "-2.2 -0.2 8.3": ["quarterlife"], "-6.6 7.9 17.1": ["estrus"], "8.7 -1.1 2.0": ["inflator"], "-5.0 1.8 9.7": ["cytogenetic"], "9.5 15.2 11.6": ["jackrabbits"], "3.2 7.0 6.9": ["madrid"], "-3.4 8.0 4.8": ["antibacterials"], "11.1 14.0 16.2": ["stirrer"], "5.1 3.9 15.0": ["spiels"], "6.3 4.6 3.2": ["forma"], "1.1 2.5 -0.6": ["onsale"], "-1.0 9.6 1.6": ["disaggregate"], "-3.7 28.6 -0.5": ["casualities"], "2.8 8.0 13.3": ["dateless"], "-3.9 20.3 5.3": ["fuzzing"], "14.5 11.9 44.1": ["narwhal"], "10.1 3.8 25.7": ["barbequed"], "38.1 13.7 31.7": ["leviathans"], "-2.0 -0.7 5.8": ["voluntourism"], "-1.6 -0.8 4.8": ["bedsits"], "7.8 12.6 5.2": ["kleptomaniac"], "5.7 9.9 15.7": ["ollie"], "6.6 1.4 1.2": ["slumbered"], "-3.5 9.1 2.1": ["underclothes"], "-0.7 6.7 9.0": ["disseminations"], "16.8 9.4 34.2": ["sealife"], "3.3 2.2 4.6": ["govenor"], "-1.8 7.5 10.6": ["antigambling"], "3.1 4.8 6.1": ["outparcels"], "-0.4 6.8 8.1": ["bene"], "12.5 10.2 9.5": ["cineplexes"], "17.5 10.4 19.4": ["jellybean"], "10.6 11.1 15.3": ["theropods"], "20.7 9.0 -1.2": ["whooshed"], "7.4 6.5 7.3": ["entrainment"], "1.6 2.5 10.2": ["steven"], "-5.9 9.4 4.8": ["reemphasized"], "10.5 3.9 8.6": ["ncaa"], "7.9 8.0 5.0": ["expecations"], "10.0 5.6 30.1": ["spaetzle"], "-5.5 10.4 7.0": ["priggish"], "-9.4 10.4 8.6": ["repoll"], "9.2 12.3 17.6": ["hollyhocks"], "4.8 14.3 11.1": ["traversal"], "1.3 8.9 -1.4": ["unkept"], "11.6 10.2 22.3": ["teaspoonful"], "2.8 1.2 3.7": ["ramipril"], "2.4 12.3 6.5": ["eugenic"], "11.7 10.1 2.6": ["joules"], "-4.6 6.7 10.2": ["footways"], "-2.3 6.2 5.8": ["supersport"], "13.1 4.4 3.7": ["maar"], "-6.3 28.5 7.8": ["demoralizes"], "9.3 13.7 2.4": ["cupholder"], "-4.4 8.8 11.3": ["tzedakah"], "1.7 10.3 20.0": ["snowsuit"], "7.0 17.3 3.4": ["adjacencies"], "-1.6 11.8 15.2": ["gossan"], "13.5 -0.6 11.3": ["zumba"], "10.7 9.7 13.1": ["rideable"], "14.7 14.0 12.2": ["gawd"], "11.4 6.2 14.9": ["bewilderingly"], "2.9 16.0 4.1": ["harrass"], "0.1 3.9 6.7": ["pharmacogenomic"], "16.7 23.2 12.6": ["petrifying"], "12.8 -0.5 5.7": ["gurgled"], "-4.2 1.1 -4.9": ["thrombolytic"], "6.0 5.7 16.7": ["sickie"], "15.4 5.4 27.5": ["dockworker"], "9.5 7.1 10.1": ["quirkily"], "5.1 0.0 -0.3": ["stewarded"], "12.9 -5.4 15.4": ["hooped"], "4.3 15.1 7.1": ["parodic"], "-9.8 8.9 2.3": ["revocable"], "-4.5 3.7 7.4": ["recapitulation"], "4.9 8.8 10.1": ["coagulate"], "21.9 -3.5 13.7": ["hf"], "3.0 9.0 8.8": ["ridin"], "-3.3 11.4 2.0": ["decreasingly"], "8.8 9.4 12.7": ["nutso"], "-1.5 11.2 8.8": ["accessorise"], "10.7 7.7 5.6": ["gooding"], "-4.8 9.1 11.3": ["progressivity"], "-4.2 -3.9 5.1": ["twoyear"], "1.6 5.3 6.6": ["attenuator"], "5.5 4.2 1.0": ["coffeemakers"], "0.7 8.6 -6.2": ["behing"], "3.7 7.3 0.0": ["calibrator"], "3.4 2.4 5.5": ["barnstorm"], "-1.5 6.8 19.1": ["enterococci"], "5.3 4.7 2.5": ["wie"], "-1.5 17.0 7.7": ["abettors"], "16.6 5.1 11.9": ["ukelele"], "13.6 9.9 9.0": ["magi"], "2.3 3.2 4.0": ["fairplay"], "10.5 15.1 13.6": ["keister"], "1.0 5.1 11.0": ["introns"], "4.0 0.9 1.1": ["aet"], "-2.8 3.1 7.8": ["subframe"], "9.0 2.9 7.1": ["pur"], "4.2 5.0 8.9": ["diapering"], "4.0 18.4 2.6": ["guidon"], "-8.2 0.2 4.5": ["additionality"], "8.1 3.7 14.3": ["impregnation"], "14.9 15.2 6.2": ["gyroscopic"], "9.1 5.6 5.4": ["barry"], "-0.2 25.5 0.6": ["datalink"], "-4.7 16.2 7.7": ["deductive"], "9.6 4.8 10.4": ["rejiggering"], "7.6 6.4 17.4": ["dilettantes"], "1.3 5.9 12.9": ["butyrate"], "1.7 15.6 11.0": ["undirected"], "6.9 3.2 13.9": ["nanos"], "13.8 6.9 1.3": ["clubroom"], "3.0 9.7 2.9": ["valence"], "8.4 20.0 15.7": ["naif"], "10.8 24.3 10.9": ["everyplace"], "11.0 17.0 13.6": ["supercooled"], "8.5 12.0 -6.5": ["ionizing"], "0.5 17.1 11.3": ["taproot"], "10.0 11.0 9.4": ["micrometres"], "23.3 4.4 20.4": ["globular"], "11.0 2.4 32.2": ["aspic"], "10.7 1.1 5.6": ["perkiness"], "13.0 17.0 18.6": ["masher"], "6.4 6.8 10.2": ["homogenize"], "4.5 21.6 6.6": ["externality"], "-5.0 0.1 9.5": ["nonstudents"], "13.4 10.8 30.0": ["profiteroles"], "-1.9 17.6 2.1": ["readier"], "-1.4 16.6 10.4": ["basestealers"], "2.6 3.8 1.0": ["dilatation"], "0.1 7.7 1.6": ["desiccant"], "4.8 21.2 5.0": ["adventurist"], "5.5 7.7 13.7": ["wristing"], "7.2 20.4 12.7": ["goalsquare"], "8.1 19.3 7.7": ["cajones"], "5.4 16.5 7.5": ["waverers"], "3.9 14.6 3.6": ["reviles"], "13.0 18.6 2.0": ["desperadoes"], "-1.0 -1.9 5.1": ["stoma"], "-8.5 4.5 9.4": ["hypertriglyceridemia"], "13.9 2.2 -2.6": ["eurocents"], "4.7 11.6 6.6": ["jackman"], "6.4 7.1 9.2": ["outof"], "5.7 9.1 -1.3": ["mailstream"], "-1.2 6.2 4.5": ["nonvolatile"], "-2.3 15.7 -5.4": ["outspokenly"], "8.7 5.0 12.3": ["pillared"], "10.3 7.3 29.7": ["carabao"], "7.4 2.5 20.4": ["luncheonette"], "-2.1 3.7 4.3": ["dielectrics"], "21.5 3.1 11.3": ["mondo"], "-2.4 13.1 14.6": ["horsetrading"], "-1.6 8.9 9.9": ["giardia"], "3.7 -2.4 3.9": ["gypped", "vk"], "12.7 8.5 7.7": ["duffs"], "7.1 7.7 5.0": ["silicates"], "-4.8 11.5 0.6": ["antimalarial"], "6.8 8.3 11.0": ["hafnium"], "5.0 5.8 16.8": ["horticulturalists"], "3.2 14.0 6.3": ["troupers"], "-5.1 12.7 1.9": ["libeling"], "3.8 2.5 11.3": ["scenester"], "20.8 12.3 9.7": ["benevolently"], "8.9 3.9 8.5": ["suctioned"], "10.5 4.8 5.1": ["phonebooks"], "-5.1 19.8 3.2": ["shouter"], "-6.7 2.1 7.1": ["clemencies"], "0.7 -1.2 3.3": ["acquis"], "-4.5 6.2 17.4": ["leucovorin"], "4.6 14.9 16.0": ["redbud"], "6.4 11.3 17.4": ["overbite"], "3.2 13.6 11.2": ["eave"], "3.7 21.6 12.2": ["ballhawk"], "-4.1 3.1 -2.0": ["answerphone"], "1.6 12.8 2.6": ["tought"], "6.0 23.3 4.7": ["obsolescent"], "7.1 16.0 4.2": ["dullard"], "-7.5 13.9 6.3": ["overwrites"], "10.6 5.8 -2.3": ["relit"], "-5.4 6.7 3.9": ["cardmember"], "9.6 6.8 14.3": ["scrapyards"], "5.5 9.2 15.8": ["spookiness"], "6.6 16.8 8.9": ["laggy"], "2.7 -6.5 -0.2": ["mentorships"], "2.4 -2.1 5.0": ["adventurousness"], "-1.6 24.6 6.4": ["exclusivist"], "4.7 3.1 10.2": ["sterols"], "11.2 8.6 11.9": ["interspecies"], "10.2 11.0 5.4": ["bugbears"], "7.5 -2.7 6.9": ["finacial"], "1.5 12.8 2.1": ["proscribes"], "1.8 2.7 6.8": ["flutists", "diethanolamine"], "9.4 25.4 16.7": ["stander"], "-7.2 5.0 -1.9": ["cardioprotective"], "-0.1 3.5 7.0": ["harrumphed"], "-0.5 9.1 11.0": ["synesthesia"], "3.2 5.5 7.7": ["brit"], "7.9 27.1 16.0": ["aerially"], "-1.5 12.4 6.0": ["joyfulness"], "10.6 4.3 13.6": ["excretions"], "-10.1 17.0 1.6": ["ascertainable"], "0.3 3.0 6.8": ["faecal"], "10.1 15.3 5.1": ["brung"], "13.3 12.9 15.5": ["irradiating"], "2.7 3.0 17.0": ["mak"], "15.6 26.9 7.3": ["jackboots"], "-5.7 17.2 4.1": ["supportability"], "4.2 -2.0 0.4": ["zur"], "1.2 6.5 5.9": ["basestations"], "9.3 4.7 4.2": ["atty"], "-3.5 7.3 -0.5": ["qualifer"], "-3.4 17.4 7.7": ["theistic"], "15.4 8.2 9.7": ["disentangled"], "8.5 3.1 4.2": ["ney"], "-0.9 4.2 9.7": ["bes"], "11.4 -3.1 15.7": ["coned"], "10.2 1.1 9.4": ["wank"], "11.7 12.3 8.9": ["smarted"], "1.2 3.2 4.4": ["unhappier", "custos"], "17.3 5.5 15.6": ["unappetising"], "9.0 15.6 11.6": ["unmeasurable"], "7.6 5.5 7.0": ["waterproofed"], "-5.6 9.2 4.6": ["timecode"], "-1.5 8.1 24.4": ["paczki"], "14.2 21.7 18.0": ["forelegs"], "-0.3 12.0 11.8": ["bosque"], "22.0 8.0 21.3": ["slurps"], "6.6 7.1 9.3": ["stouter"], "12.8 15.0 10.2": ["alps"], "10.4 20.3 5.7": ["loots"], "10.8 10.0 10.6": ["sippers"], "2.5 3.6 11.6": ["jerrycans"], "4.0 11.7 9.6": ["urbanizing"], "7.3 17.4 11.2": ["shiv"], "9.5 9.0 6.9": ["catnap"], "2.8 5.9 12.9": ["parishoners"], "-0.6 -0.5 1.4": ["cetrorelix"], "2.9 7.9 10.1": ["hayfields"], "6.3 -2.3 0.8": ["turbomachinery"], "6.2 12.1 3.8": ["loftily", "synvolcanic"], "-2.5 16.3 0.4": ["peole"], "10.8 11.7 12.3": ["cosmically"], "3.2 9.9 2.9": ["orients"], "5.1 15.1 12.8": ["lowballing"], "-6.0 11.7 -2.2": ["hereto"], "13.4 11.9 2.5": ["dustbowl"], "-10.2 9.3 14.7": ["scullers"], "11.6 4.8 7.2": ["primly"], "13.9 6.0 28.1": ["turducken"], "12.8 5.3 25.2": ["votives"], "-0.4 12.2 2.6": ["shies"], "2.5 1.0 8.0": ["flibanserin"], "13.9 20.1 36.1": ["knotweed"], "10.6 8.2 0.7": ["demotes"], "7.4 24.8 8.2": ["smiting"], "-1.8 6.7 20.7": ["sheens"], "3.4 8.5 7.6": ["homologous"], "2.4 4.5 4.0": ["virtualise"], "2.3 25.9 -2.0": ["libels"], "-5.4 7.1 9.8": ["aneuploidy"], "-3.8 6.9 10.6": ["stagy"], "2.6 4.1 5.2": ["remaster"], "13.7 8.6 18.5": ["yule"], "6.6 20.9 5.4": ["bumbler"], "5.9 12.9 20.0": ["pilothouse"], "3.3 -2.2 17.6": ["rin"], "13.6 4.1 10.4": ["eee"], "5.5 7.2 6.8": ["constructivist"], "-3.3 1.7 3.4": ["optocouplers"], "-0.3 -5.0 8.5": ["madras"], "3.1 10.7 9.2": ["partyroom"], "2.0 -2.5 9.7": ["ating"], "15.2 12.5 10.9": ["effin"], "-0.3 16.4 -1.7": ["misapprehensions"], "-0.2 7.3 12.9": ["interbred"], "2.9 2.4 9.9": ["wilson"], "-2.4 -1.7 6.3": ["zirconia"], "10.9 4.2 9.7": ["fireplug"], "4.5 5.6 4.5": ["pericarditis"], "0.9 9.8 12.9": ["flakiness"], "4.4 -0.9 14.3": ["streetwalker"], "-2.4 11.9 9.2": ["thermocouples", "phenomenonal"], "-8.6 7.0 4.6": ["appealability"], "2.2 -1.5 24.9": ["carcase"], "-4.4 3.5 7.2": ["ascites"], "-1.7 13.8 42.8": ["brookies"], "-1.7 14.3 12.6": ["hooning"], "6.1 5.8 3.8": ["preperation"], "14.5 11.9 20.1": ["handsaw"], "7.6 5.8 7.6": ["mismatching"], "2.2 4.8 7.4": ["oustees"], "5.4 6.4 0.5": ["surefooted"], "10.1 1.5 10.1": ["brazilian"], "0.6 6.1 11.6": ["hyperplasia"], "8.5 37.9 6.3": ["counterstrike"], "13.7 11.5 29.3": ["booby"], "-0.7 17.8 13.9": ["overwater"], "15.0 6.3 31.3": ["gluey"], "18.2 18.6 10.8": ["disgustedly"], "-2.8 5.0 6.0": ["apical"], "5.6 7.1 16.8": ["snackers"], "7.6 7.2 7.9": ["homeopaths"], "-1.1 -1.4 3.5": ["microlenders"], "14.5 -1.9 0.4": ["midstage"], "2.1 1.3 11.2": ["makai"], "9.2 13.4 6.9": ["moaners"], "6.1 4.3 15.7": ["euthanased", "fibulin"], "1.1 11.7 7.6": ["deicer"], "8.5 3.0 13.1": ["batching"], "0.6 -3.4 17.1": ["stockers"], "11.5 8.1 7.0": ["classifier"], "19.2 11.5 10.3": ["apprehensively"], "8.7 1.9 11.2": ["wisecracked"], "0.2 -4.7 12.3": ["embalmers"], "4.3 13.3 6.2": ["denialist"], "-0.9 -0.0 9.3": ["novation"], "-0.4 6.6 4.4": ["witholding"], "12.4 13.2 7.3": ["unsociable"], "18.4 11.9 20.8": ["bloomin"], "11.6 5.0 13.4": ["lumberyards"], "14.6 16.9 12.4": ["warrens"], "-10.9 17.4 -1.2": ["constitutionalists"], "-5.7 10.2 5.5": ["sacrum"], "12.6 9.8 22.3": ["doubloons"], "20.5 9.7 23.6": ["ahoy"], "1.7 14.0 10.9": ["invariant"], "10.4 3.9 22.1": ["pearlescent"], "4.0 17.8 18.7": ["fertilizes"], "-2.4 4.0 11.6": ["splainin"], "-5.0 16.0 -0.3": ["nonjudicial"], "19.6 14.2 15.4": ["parasitical"], "5.0 7.4 5.3": ["belabored"], "9.6 3.1 21.7": ["guinea"], "5.3 12.5 8.0": ["undoubtably"], "-4.7 11.2 6.6": ["kashmir"], "7.1 7.6 -1.9": ["convertor"], "-6.8 9.0 17.0": ["fusarium"], "8.5 4.1 15.4": ["wor"], "0.7 1.7 13.8": ["enamels"], "-3.0 8.3 10.2": ["conversationally"], "-6.1 6.9 19.1": ["lucerne"], "-9.0 13.6 2.4": ["thundershower"], "1.3 14.7 5.0": ["psychoanalysts"], "5.2 13.8 10.7": ["metalhead"], "-5.8 5.6 5.2": ["clonidine"], "4.4 12.4 12.7": ["mafiosi"], "1.3 1.1 11.9": ["phenolic"], "-2.3 10.6 11.3": ["shigella"], "8.8 8.8 8.2": ["merchandises"], "-1.2 10.1 9.0": ["chilliest"], "7.8 20.8 5.3": ["fantasists"], "16.5 4.7 17.5": ["mylar"], "4.9 -5.3 5.2": ["bel"], "7.1 12.9 3.4": ["whcih"], "4.7 20.6 18.7": ["acquiesces"], "-1.3 14.5 12.5": ["geniality"], "5.5 7.9 3.4": ["outblocked"], "11.6 14.9 13.2": ["fancifully"], "-3.2 1.7 4.6": ["coun"], "-5.0 9.9 0.3": ["underserviced"], "11.1 7.0 26.8": ["rex"], "2.9 17.0 4.5": ["unmoderated"], "2.4 7.0 13.9": ["rebalances"], "-7.2 15.1 13.4": ["recitative"], "-3.4 21.1 1.6": ["collaborationist"], "0.7 5.5 4.7": ["likey"], "-0.6 10.5 8.5": ["hyperextension"], "2.9 2.0 6.1": ["kroon"], "-1.6 1.1 15.9": ["georgette"], "12.8 4.6 16.9": ["glasshouses"], "12.6 19.4 14.1": ["chimerical"], "3.7 11.3 15.4": ["scratchcard"], "-1.8 22.5 9.6": ["nuclearization"], "-22.4 9.5 -1.0": ["rearrest"], "-4.0 0.7 2.2": ["semiannually"], "9.9 29.8 5.2": ["implacably"], "18.0 -4.5 7.8": ["kickstarts"], "5.6 28.1 4.5": ["destruct"], "18.0 21.4 9.5": ["harpies"], "2.8 3.9 22.6": ["maine"], "-1.9 7.4 9.1": ["coverall"], "-5.0 7.7 0.7": ["telecasted"], "6.5 10.4 -4.9": ["inveighed"], "4.8 8.8 6.4": ["augmentations"], "3.5 11.0 12.3": ["folksiness"], "2.4 25.1 6.5": ["unguardable"], "3.8 15.9 11.5": ["advisedly"], "18.2 3.2 5.1": ["captial"], "4.4 1.5 17.3": ["william"], "-0.4 15.6 7.4": ["aridity"], "-10.6 5.5 -1.4": ["stepfamilies"], "5.6 4.8 23.5": ["cycads"], "3.5 22.3 3.7": ["blindsiding"], "-2.0 2.5 0.7": ["technetium"], "-12.0 3.2 6.0": ["neuropathology"], "4.9 6.3 12.1": ["hostelries"], "5.9 -0.6 20.6": ["liang"], "15.2 13.7 39.3": ["goby"], "9.3 5.4 6.1": ["prurience"], "3.2 0.5 6.9": ["courtships"], "-1.4 8.1 10.1": ["lexicographers"], "6.9 5.6 34.2": ["tostadas"], "7.5 0.9 9.2": ["sunshiny"], "-0.7 3.0 38.0": ["escarole"], "-2.6 5.3 0.3": ["oped"], "2.9 9.2 32.4": ["redear"], "1.9 4.9 4.2": ["patronizes"], "1.7 0.0 7.3": ["finishings"], "3.8 14.1 4.3": ["externalize"], "20.0 16.1 12.2": ["limbless"], "-3.1 -2.0 0.5": ["secondments"], "3.3 5.4 6.0": ["hyperventilated"], "7.6 -1.2 4.2": ["reinitiated"], "12.2 9.4 5.4": ["unchartered"], "-1.0 18.3 6.2": ["unchristian"], "4.9 8.4 15.4": ["simon"], "4.4 20.3 8.9": ["existentially"], "9.9 13.5 15.9": ["lollygagging"], "-3.2 11.3 8.6": ["respites"], "3.4 5.4 1.1": ["biodegradability"], "10.8 16.5 7.9": ["hallucinated"], "8.3 7.6 5.1": ["boxier"], "14.5 4.2 16.9": ["basketful"], "10.9 5.3 7.8": ["zigs"], "5.4 14.0 8.6": ["misjudgements"], "-6.7 7.0 8.5": ["arroyos"], "-6.7 7.6 7.6": ["titer"], "5.9 14.9 11.0": ["doorbuster"], "2.2 -1.6 7.5": ["prov"], "8.0 18.5 8.8": ["backlines"], "-1.5 14.8 23.2": ["tenderize"], "20.5 11.3 24.9": ["viking"], "10.6 15.3 19.1": ["rana"], "5.6 1.7 6.5": ["preprint"], "19.0 23.3 8.9": ["bejeezus"], "14.6 5.4 20.3": ["peckish"], "5.2 16.7 11.5": ["setpieces"], "7.6 1.2 13.5": ["evaporators"], "9.6 23.3 10.8": ["foulest"], "0.1 14.4 41.6": ["soba"], "-1.7 4.8 12.9": ["sherwani"], "6.1 8.1 5.0": ["jives"], "-7.4 3.4 6.0": ["herniation"], "2.5 13.6 14.0": ["helmsmen"], "11.3 18.4 0.1": ["taxmen"], "1.9 12.2 2.8": ["defintely"], "-13.1 2.5 6.5": ["subspecialists"], "21.3 6.9 13.0": ["yodelling"], "-2.4 33.8 4.8": ["paratroops"], "-11.0 6.2 -1.5": ["rerecorded"], "2.2 11.7 8.5": ["phished"], "-9.0 -1.3 0.8": ["hepatotoxicity"], "8.3 3.5 8.8": ["doublewide"], "9.0 8.0 15.3": ["eccentrically"], "1.9 11.9 14.9": ["grassing"], "13.0 10.1 13.9": ["piggybank"], "-2.3 13.0 7.2": ["nurturers"], "0.9 1.5 3.8": ["handsprings"], "-2.8 20.0 11.3": ["riseball"], "11.7 13.2 21.6": ["salvagers"], "-3.6 6.8 8.6": ["codesharing"], "10.7 15.4 12.6": ["primitivism"], "10.4 8.4 4.7": ["dowsing"], "7.3 12.8 3.0": ["signalers"], "-9.2 1.6 0.7": ["underuse"], "0.3 9.4 2.5": ["equivalently"], "14.7 5.8 4.0": ["shhh"], "1.7 6.4 11.8": ["overstocking"], "7.2 7.9 13.8": ["schoolmarm"], "2.5 4.1 7.4": ["summarization"], "4.2 -3.6 15.7": ["plaits"], "25.1 2.7 14.9": ["largish"], "-8.5 5.1 10.2": ["apheresis"], "-0.1 12.8 -3.5": ["edify"], "-10.6 6.2 9.9": ["ribbies"], "11.0 4.1 5.9": ["bucketloads"], "27.7 6.2 23.0": ["gumdrops"], "12.5 11.3 11.3": ["greenskeeper"], "3.9 6.8 1.5": ["electrophysiological"], "-5.0 11.0 -1.2": ["undramatic"], "2.3 -0.2 6.6": ["nonhazardous"], "1.9 6.4 4.2": ["mainman"], "7.8 3.4 13.6": ["jollity"], "14.6 14.1 18.0": ["speckle"], "-2.2 5.4 9.3": ["kudo"], "-2.4 4.6 -2.9": ["confounders"], "1.7 5.1 9.9": ["agers"], "1.8 11.4 7.2": ["footlocker"], "-6.0 10.6 2.3": ["inerrancy"], "4.9 1.0 22.3": ["carcases"], "-8.9 4.9 0.1": ["cosigner"], "-9.7 -9.5 10.0": ["reinstatements"], "-0.3 5.7 9.2": ["wirehouse"], "-5.1 -3.7 0.9": ["zidovudine"], "2.6 7.5 6.2": ["windproof"], "4.0 10.6 16.9": ["clarifier"], "9.9 15.4 34.9": ["thresher"], "8.8 7.2 2.1": ["vom"], "-3.9 4.0 7.3": ["hillclimb"], "2.5 6.6 19.5": ["champers"], "-6.0 1.2 5.3": ["dissolutions"], "2.7 12.8 2.6": ["flareups"], "-1.6 3.1 -0.3": ["leuprolide"], "12.5 12.1 16.3": ["gots"], "14.2 9.0 4.9": ["multimillions"], "1.4 3.5 10.5": ["definitly"], "3.2 4.1 10.2": ["davis"], "4.9 10.2 13.1": ["patrick"], "2.6 6.5 11.0": ["teamster"], "7.4 3.2 3.8": ["diversely"], "15.6 7.5 3.1": ["slaloming"], "4.6 16.5 7.8": ["unmapped"], "1.3 6.9 39.6": ["manicotti"], "-4.7 11.4 6.0": ["mitoxantrone"], "-1.0 15.8 9.7": ["neuraminidase"], "-1.5 6.9 8.3": ["halogens"], "-0.9 1.6 15.1": ["burgh"], "-6.4 10.5 7.5": ["yatris"], "0.1 0.1 13.5": ["solariums"], "6.8 8.9 7.5": ["sourly"], "-8.0 -1.0 8.8": ["laicized"], "1.1 2.9 26.0": ["herby"], "11.7 -1.5 12.4": ["barnet"], "16.0 10.4 13.1": ["coalmining"], "-1.7 8.2 -1.3": ["remeber"], "-0.2 -0.8 -0.5": ["persue"], "-4.0 3.1 2.5": ["dimebon"], "16.7 11.4 8.9": ["totters"], "-7.6 16.5 9.4": ["dps"], "3.4 6.7 9.9": ["reprofiling"], "-2.2 12.0 14.3": ["joviality"], "-2.8 10.1 5.4": ["dropbacks"], "-6.6 3.6 9.5": ["moxifloxacin"], "0.7 14.8 2.2": ["continuities"], "7.5 11.6 10.3": ["tastelessness"], "5.9 3.1 27.5": ["scrimshaw"], "6.5 15.9 12.8": ["scourging"], "12.5 -2.6 14.6": ["multistep"], "4.1 7.1 7.6": ["tryscorer"], "7.9 8.5 4.7": ["modellers"], "-1.7 4.9 11.6": ["reassortment"], "9.9 10.2 11.3": ["lordly"], "5.0 2.1 10.1": ["confabs"], "-8.6 1.9 5.1": ["arrearage"], "11.5 12.1 17.0": ["parson"], "5.0 1.7 12.6": ["palsy"], "-0.9 15.1 11.8": ["alkaloid"], "31.3 5.4 17.6": ["gigantism"], "17.1 2.5 12.2": ["unfeasibly"], "16.4 12.0 11.2": ["hypochondriacs"], "2.2 3.8 25.1": ["farmgate"], "9.1 5.0 0.6": ["begot"], "6.7 8.8 2.8": ["childen"], "9.5 3.6 -1.0": ["sweatbands"], "12.2 20.6 29.6": ["baiters"], "-2.6 6.6 2.6": ["alveolar"], "8.4 7.1 13.2": ["cosmo"], "-1.0 6.0 4.1": ["microdisplays"], "9.7 10.4 7.9": ["excitements"], "2.3 2.8 6.7": ["impecunious"], "13.9 1.6 1.5": ["dissolvable"], "3.5 6.1 8.3": ["imbizo"], "5.4 12.7 2.2": ["persistant"], "-3.8 18.7 -0.2": ["excoriates"], "17.0 7.0 3.5": ["cannibalised"], "6.5 5.0 12.3": ["rar"], "5.3 -0.8 -0.7": ["alfimeprase"], "-15.7 2.4 4.9": ["episiotomy"], "-1.8 9.6 9.3": ["dunam"], "11.6 10.3 10.5": ["energetics"], "-1.4 -5.5 4.1": ["nonmusical"], "4.6 2.1 6.8": ["chimeric"], "4.2 -0.5 8.5": ["templating"], "5.2 -2.9 13.0": ["hy"], "0.1 5.7 2.4": ["notifiable"], "8.1 2.5 6.9": ["sweatband"], "-6.6 4.9 10.3": ["actuarially"], "-4.2 8.8 -1.3": ["bronchiectasis"], "2.7 -0.2 8.7": ["plotless"], "5.6 30.1 9.0": ["calvary"], "6.7 5.7 4.0": ["soundtracked"], "14.0 2.6 11.8": ["weightiest"], "-2.6 11.3 14.9": ["ivermectin"], "5.2 2.5 12.3": ["hjp"], "1.1 13.5 14.8": ["monsoonal"], "7.2 22.8 8.0": ["spacebar"], "1.7 19.7 6.4": ["compartmentalizing"], "-0.2 0.5 8.9": ["offramps"], "10.9 10.4 15.9": ["fop"], "8.8 9.4 18.4": ["pushbike"], "7.3 7.5 5.0": ["footrests"], "10.1 9.6 19.2": ["cupful"], "-3.8 15.0 7.6": ["conservations"], "15.4 2.3 6.9": ["allegra"], "2.4 2.1 3.8": ["rummages"], "20.6 7.9 7.7": ["flatscreen"], "1.9 20.8 10.0": ["calculable"], "-3.0 13.4 0.9": ["saab"], "3.4 6.7 10.3": ["circumferential"], "1.6 7.4 1.9": ["debiting"], "6.4 7.1 32.2": ["kabob"], "7.0 18.9 14.8": ["byplay"], "-5.0 6.7 0.3": ["covariates"], "-0.3 0.6 3.5": ["ocassion"], "-6.2 0.7 6.0": ["mmscfd"], "-5.4 7.5 -0.3": ["midpack"], "-0.6 6.1 17.5": ["tripper"], "-3.1 16.8 3.7": ["tenaciousness"], "-3.8 5.8 2.7": ["todate"], "-3.0 23.6 8.1": ["dhimmi"], "10.9 4.4 11.1": ["tatted"], "3.2 14.2 7.2": ["arithmetical"], "14.3 10.7 17.0": ["airwave"], "-3.3 2.9 7.2": ["boxscores"], "-4.5 8.5 -3.9": ["communiqu"], "4.2 -0.4 4.6": ["pictorials"], "11.7 5.1 19.5": ["punchbowl"], "-1.5 -0.6 2.7": ["kpl"], "11.0 20.1 10.2": ["promiscuously"], "-14.8 3.8 -0.5": ["principalship"], "-0.2 5.1 9.4": ["dimer"], "-3.9 12.9 16.7": ["uncalculated"], "8.1 7.6 36.0": ["sago"], "5.5 2.7 10.5": ["sot"], "11.4 11.9 18.6": ["reattaching"], "5.4 10.5 18.4": ["diggin"], "2.9 9.3 6.4": ["hayloft"], "2.2 -0.3 13.2": ["kirk"], "9.6 10.3 3.8": ["suppository"], "9.6 11.3 9.1": ["predominating"], "6.6 18.4 15.8": ["territoriality"], "-1.9 8.0 8.2": ["preheating"], "4.1 13.0 1.4": ["bednets"], "22.4 10.5 8.3": ["afficionados"], "9.0 10.7 26.7": ["tope"], "15.4 6.9 4.0": ["eureka"], "10.1 2.0 8.4": ["glossaries"], "23.0 18.8 20.5": ["meanies"], "-1.9 3.6 3.7": ["flatted"], "-1.5 4.2 5.4": ["faders"], "3.6 5.8 4.2": ["benifit"], "6.1 19.8 5.9": ["onrush"], "4.2 7.8 9.3": ["mapper"], "7.4 10.6 10.5": ["wheres"], "-0.7 11.0 10.2": ["proscriptions"], "4.8 15.0 1.0": ["orientate"], "4.2 16.3 6.1": ["flopper"], "-9.2 12.4 -0.7": ["unsworn"], "1.7 8.1 -1.4": ["internalisation"], "-4.3 -0.1 -0.3": ["liase"], "6.6 20.5 -1.1": ["incitements"], "-8.6 -3.6 -2.7": ["reaccredited"], "-3.2 6.5 7.7": ["sportscast", "saath"], "-2.1 19.5 6.9": ["fraternize"], "-1.4 11.2 6.2": ["photodiode"], "9.5 11.7 1.6": ["wrests"], "7.3 13.5 11.0": ["plebs"], "17.6 3.4 5.3": ["alluringly"], "6.6 9.1 14.7": ["glycans"], "6.7 5.3 10.7": ["straitlaced"], "3.7 9.1 1.9": ["intersting"], "11.1 4.2 11.8": ["layabouts"], "9.2 4.2 28.8": ["vittles"], "18.0 7.3 10.0": ["cavorts"], "15.1 11.7 9.7": ["unassembled"], "5.1 -7.1 3.5": ["conduced"], "4.7 10.1 10.1": ["ssh"], "8.9 3.1 1.6": ["undernoted"], "8.4 20.8 16.7": ["legdrop"], "4.2 7.1 17.4": ["glycoproteins"], "0.7 12.4 24.1": ["denning"], "1.6 17.3 1.4": ["geotag"], "9.3 0.7 2.4": ["schoolbags"], "14.6 5.7 12.0": ["scrooge"], "10.2 5.6 8.6": ["msnbc"], "4.6 16.8 4.5": ["rangefinder"], "3.0 13.3 2.7": ["protectant"], "11.5 5.1 -2.0": ["useage"], "5.5 16.5 6.0": ["fansites"], "-6.0 14.7 11.5": ["introversion"], "9.8 12.5 17.5": ["transfats"], "14.1 19.7 9.9": ["cravenly"], "8.2 9.7 4.7": ["overcompensation"], "1.7 6.6 8.7": ["meetups"], "2.5 4.3 7.3": ["pattas"], "-2.4 6.3 1.1": ["kabbalah"], "-0.3 2.1 -2.0": ["channelised"], "5.5 10.7 0.9": ["ustekinumab"], "7.8 13.9 11.7": ["horizontals"], "-0.6 4.0 -2.9": ["mann"], "5.0 15.3 26.5": ["weedlines"], "-9.5 11.2 -1.7": ["stepfathers"], "-7.0 -0.2 -0.0": ["preamplifier"], "0.3 13.3 1.8": ["predicates"], "-0.2 0.4 9.1": ["pipettes"], "-2.8 8.8 27.1": ["salvias"], "-1.6 0.8 -4.5": ["coeditor"], "4.6 31.2 3.2": ["spymasters"], "-2.2 8.9 13.2": ["tubewell"], "24.1 20.7 10.4": ["centaurs"], "16.8 17.7 10.7": ["megaton"], "13.7 9.8 32.6": ["bittern"], "2.2 8.4 4.1": ["biochemically"], "-0.3 9.8 -0.3": ["particuarly"], "3.9 15.0 11.4": ["cads"], "9.8 20.3 1.7": ["literalism"], "16.9 8.1 18.0": ["rumps"], "9.8 -2.7 7.7": ["bidded"], "-2.6 8.8 0.3": ["outstations"], "11.2 8.1 13.8": ["indulgently"], "7.9 4.0 -0.3": ["prescreen"], "4.9 4.5 -3.7": ["hier"], "6.3 7.3 10.8": ["waitin"], "13.5 14.8 12.3": ["umbra"], "-1.3 17.5 12.8": ["oppo"], "17.3 9.3 19.8": ["danish"], "5.3 10.5 32.1": ["swimbait"], "11.4 18.8 11.6": ["hallow"], "-5.5 7.8 17.7": ["repotting"], "8.5 14.5 14.9": ["forelimbs"], "4.1 16.8 10.9": ["tramper"], "3.6 2.0 5.4": ["magnesia"], "5.6 16.5 8.7": ["plunders"], "-14.0 5.3 -2.8": ["thiazolidinediones"], "0.7 5.1 26.3": ["pinto"], "5.7 7.0 10.5": ["clangers"], "3.6 15.3 8.4": ["ridgetop"], "9.7 3.2 7.2": ["keeling"], "8.5 19.3 4.1": ["blackball"], "11.9 10.0 30.5": ["untagged"], "-4.8 -1.2 3.3": ["ubroadcast"], "-8.5 6.9 9.7": ["lh"], "2.7 23.9 3.3": ["harassers"], "4.4 12.7 11.4": ["repellants"], "4.4 1.6 10.3": ["pj"], "1.2 9.4 8.9": ["testiness"], "9.0 13.5 8.4": ["controling"], "1.1 0.2 5.0": ["agus"], "5.8 4.6 9.3": ["ejecta"], "-7.1 4.6 10.8": ["microalbuminuria"], "17.2 8.8 8.8": ["holic"], "-0.5 7.6 4.8": ["dueted"], "-1.6 6.5 2.6": ["recapitulate"], "5.3 5.3 9.2": ["forcast"], "5.9 1.3 10.9": ["gamine"], "7.9 -1.5 13.8": ["taquerias"], "8.3 6.6 5.2": ["thecountry"], "11.4 -0.4 5.4": ["synthesisers"], "1.5 3.8 18.9": ["silversmiths"], "9.4 3.5 18.4": ["mus"], "8.6 2.8 10.1": ["pursestrings"], "0.3 7.1 1.9": ["smurfing"], "2.5 9.1 12.4": ["salivary"], "15.2 23.6 8.3": ["corporatists"], "-0.0 2.2 3.2": ["sukuks"], "4.3 -4.6 0.6": ["commisioner"], "16.3 14.3 5.9": ["oligopolistic"], "9.1 9.2 7.7": ["obnoxiousness"], "-2.5 15.0 0.8": ["actualizing"], "3.8 7.8 8.2": ["checkboxes"], "23.6 13.0 22.6": ["anacondas"], "10.9 19.7 8.3": ["devestating"], "4.4 11.1 10.2": ["grindcore"], "1.6 13.0 1.5": ["mobilisations"], "2.6 13.6 4.4": ["aberrational"], "-3.0 13.1 3.4": ["abridgement"], "-3.1 4.5 -1.7": ["ern"], "12.9 0.6 6.9": ["raisings"], "-2.8 -4.4 -4.4": ["citied"], "5.1 11.7 2.5": ["dioxide"], "6.6 7.1 7.3": ["grandiloquent"], "12.4 -2.7 21.5": ["noshed"], "1.5 -0.8 10.1": ["wwe"], "13.4 0.4 28.2": ["taquitos"], "8.7 14.2 6.1": ["unshielded"], "12.4 3.1 5.2": ["gravure"], "11.0 -2.4 7.2": ["lire"], "1.1 5.6 12.4": ["weatherproofing"], "-1.0 6.3 1.1": ["draftsmen"], "7.0 3.6 15.4": ["haciendas"], "-0.4 3.4 -1.2": ["atazanavir"], "-6.0 4.2 3.5": ["neoplasms"], "5.0 19.7 8.5": ["baser"], "3.7 13.0 -2.4": ["misstates"], "4.5 17.7 3.3": ["paranoiac"], "10.5 2.0 15.8": ["sty"], "17.3 3.9 18.7": ["disney"], "3.3 21.0 7.4": ["deducing"], "25.3 17.6 5.7": ["phalanxes"], "4.3 11.3 9.0": ["haveli"], "10.7 5.2 12.9": ["anatomist"], "0.8 4.5 19.2": ["lisa"], "-4.1 5.4 6.1": ["furans"], "7.0 9.2 14.5": ["grogginess"], "-3.1 15.9 11.1": ["grafter"], "4.2 0.0 5.9": ["nanocomposite"], "-2.9 12.6 7.7": ["palpation"], "6.4 14.3 22.9": ["mulberries"], "-5.3 7.1 1.4": ["resentence"], "-3.9 16.0 8.8": ["hypercritical"], "5.7 5.3 3.4": ["scrappier"], "1.7 -1.5 17.0": ["espadrilles"], "1.1 6.0 5.5": ["microliter"], "8.8 1.2 6.4": ["reconceived"], "2.7 7.6 7.2": ["touchlines", "intracerebral"], "5.2 11.1 25.6": ["yachties"], "-2.5 21.0 22.0": ["pigweed"], "4.8 11.2 6.5": ["idlers"], "22.4 13.2 9.9": ["greediest"], "3.1 1.7 11.1": ["allegro"], "10.1 11.5 11.3": ["cenbank"], "0.8 0.2 36.3": ["pappardelle"], "6.3 4.8 12.4": ["limestones"], "10.8 5.5 13.5": ["biddy"], "-2.2 10.7 4.4": ["disjunction"], "3.8 17.3 6.1": ["entreat"], "-0.4 11.8 8.1": ["evapotranspiration"], "-2.0 8.8 10.6": ["pyrethrum"], "2.6 6.3 -2.2": ["spates"], "14.8 5.4 13.3": ["kinked"], "1.0 5.3 8.4": ["translocated"], "16.4 18.6 6.1": ["pervs"], "-0.9 -2.8 2.4": ["hydrogels"], "10.4 0.9 9.2": ["opals"], "-3.1 -0.9 11.1": ["snowcoaches"], "-1.9 3.6 18.0": ["harbourmaster"], "8.4 15.0 23.7": ["langurs"], "19.0 19.0 12.2": ["zeppelins"], "-10.4 -1.3 7.0": ["multitrack"], "-0.9 4.6 7.3": ["transplantations"], "14.4 5.0 20.4": ["candyfloss"], "8.0 5.2 -2.7": ["digitalised"], "15.8 6.5 30.7": ["jigged"], "13.9 10.0 31.6": ["moa"], "7.1 5.5 19.2": ["tenderer"], "19.9 9.8 24.4": ["pavlova"], "-4.9 0.7 5.0": ["interop"], "16.3 2.0 12.9": ["oi"], "7.6 20.4 8.1": ["cybercriminal"], "6.3 5.4 17.3": ["beatniks"], "1.4 9.9 8.6": ["maters"], "7.1 11.5 1.8": ["homebase"], "-7.3 0.1 1.7": ["monthlies"], "5.4 13.7 -0.9": ["inure"], "2.6 2.7 18.1": ["nonferrous"], "10.8 0.4 12.7": ["schwag"], "-4.4 4.6 3.1": ["supernumerary"], "2.8 6.4 15.0": ["daw"], "4.9 3.7 4.5": ["breeched"], "4.4 9.9 11.2": ["sozzled"], "6.1 10.1 9.2": ["seeders"], "-1.4 -3.1 12.4": ["sina"], "6.2 8.9 25.0": ["poled"], "3.4 -4.8 6.6": ["cas"], "9.4 4.9 13.5": ["bandaid"], "16.7 8.5 13.3": ["hairiest"], "-2.1 8.0 -1.4": ["enfranchise"], "13.2 5.3 22.7": ["loincloths"], "-0.1 10.2 11.6": ["predications"], "0.5 -2.1 11.0": ["megalitre"], "8.6 24.7 12.5": ["hirelings"], "7.5 20.4 26.4": ["gook"], "14.2 3.4 10.5": ["aholic"], "-7.0 -3.5 13.3": ["probations"], "-3.8 5.8 2.4": ["revaluate"], "6.9 21.9 -0.3": ["reconquer"], "11.9 9.0 13.0": ["gibbering"], "3.7 4.1 4.3": ["sterilizes"], "5.3 8.1 23.0": ["kudu"], "-8.8 8.2 8.8": ["polyamory"], "1.7 13.7 4.8": ["frontcourts"], "7.8 -3.3 14.4": ["lactoferrin"], "11.9 17.7 8.8": ["reprobates"], "6.8 7.4 10.0": ["gayer"], "17.1 16.0 5.0": ["mutely"], "13.9 8.0 8.4": ["maladroit"], "-0.2 5.3 1.7": ["hatrick"], "11.3 4.5 2.8": ["procurer"], "6.5 9.9 9.8": ["keith"], "3.1 1.1 8.0": ["saleroom", "overfund"], "-1.8 7.1 10.2": ["adenoma"], "-2.0 0.8 3.3": ["seconder"], "13.6 15.6 8.6": ["oligopolies"], "15.5 11.7 13.3": ["swingset"], "3.4 1.9 -0.7": ["mechatronic"], "-10.0 -0.5 -2.4": ["deputations"], "16.1 29.5 2.1": ["hyperspace"], "20.8 -2.6 15.3": ["shoed"], "-5.7 11.2 4.5": ["undoable"], "14.4 17.1 6.5": ["commandeers"], "5.9 9.0 28.0": ["shrooms"], "15.2 4.3 6.9": ["ripoffs"], "18.0 -2.8 1.2": ["aan"], "8.7 3.1 2.9": ["outranking"], "4.8 7.6 15.6": ["sibs"], "0.4 8.0 -4.4": ["ordinariate"], "13.8 -1.9 14.7": ["mislabelled"], "-9.0 3.1 25.8": ["dalo"], "8.8 8.4 12.9": ["gratifyingly"], "18.4 3.5 14.5": ["spooling"], "-2.5 3.1 3.2": ["fued"], "-2.1 18.7 17.2": ["displeases"], "-4.6 -0.6 9.8": ["longform"], "9.3 11.6 23.2": ["cheeseball"], "16.5 6.5 13.9": ["sharpish"], "-2.8 4.8 12.8": ["iodide"], "5.2 9.1 10.4": ["litte"], "3.0 9.1 -2.0": ["embarrased"], "7.0 17.8 7.4": ["deathless"], "-2.2 17.8 3.7": ["mutagenic"], "8.6 6.2 6.2": ["straightness"], "19.6 18.5 25.6": ["ladybirds"], "13.5 4.2 17.1": ["hentai"], "0.2 3.1 -3.6": ["professionalisation"], "-0.1 3.0 16.0": ["cy"], "3.6 9.8 8.3": ["dil"], "13.7 -2.7 6.2": ["orig"], "-3.5 6.7 6.0": ["tenser"], "1.5 4.7 3.4": ["wangled"], "5.7 2.5 7.9": ["medi"], "1.1 2.2 6.7": ["neurophysiology"], "-2.7 1.4 13.1": ["trousseau"], "-6.4 12.4 14.6": ["chloramine"], "2.7 6.7 11.7": ["caulked"], "4.5 3.4 3.2": ["rockumentary"], "-5.0 3.0 11.2": ["comping"], "9.4 8.0 17.1": ["nuggety"], "-6.2 3.3 5.6": ["representativeness"], "4.9 20.6 9.1": ["bacillus"], "-2.2 8.8 9.1": ["tesetaxel"], "4.1 1.6 4.6": ["digitizers"], "4.1 11.7 2.1": ["globetrotters"], "5.7 10.2 16.5": ["cunnilingus"], "1.4 -1.6 2.6": ["loaners"], "16.1 17.3 4.6": ["supercop"], "6.1 18.5 6.5": ["slipup"], "7.2 10.8 16.9": ["slappers"], "9.2 8.6 10.2": ["riskless"], "-6.8 3.9 4.3": ["reinterred"], "5.7 22.4 9.2": ["normals"], "15.0 5.8 2.7": ["nationalisations"], "-4.1 1.5 -0.3": ["catechetical"], "-7.9 8.7 3.3": ["meaningfulness"], "8.0 15.4 9.0": ["fixates"], "7.0 5.7 7.6": ["levering"], "4.4 26.7 10.8": ["ferociousness"], "17.1 8.1 9.2": ["clatters"], "14.6 10.8 11.1": ["mewling"], "5.4 4.7 9.9": ["tabulators"], "7.4 5.3 13.9": ["electroclash"], "18.4 9.0 18.2": ["mmmm"], "-2.7 7.9 12.3": ["diverticulosis"], "8.1 7.2 6.9": ["mangles"], "-11.9 6.3 10.3": ["pegloticase"], "20.3 9.4 22.6": ["archipelagos"], "3.4 12.2 14.6": ["doggerel"], "2.7 23.1 3.5": ["dhimmitude"], "-3.3 8.6 2.1": ["osteotomy"], "4.3 -1.0 10.7": ["handcarts"], "-6.7 7.2 12.5": ["mumblecore"], "-1.1 4.0 12.2": ["woollens"], "7.7 15.5 25.3": ["lockjaw"], "1.3 9.7 7.1": ["formalist"], "1.7 8.3 6.2": ["mj"], "-4.7 8.8 2.8": ["amnestied"], "5.5 21.2 -0.4": ["lionize"], "10.1 6.8 37.5": ["remoulade"], "-11.8 12.4 3.6": ["recidivists"], "1.8 6.5 8.3": ["semiarid"], "5.2 12.4 14.2": ["nerdiness"], "-4.2 0.1 12.3": ["kitesurfing"], "12.4 -0.2 11.6": ["gangbuster"], "14.0 19.9 12.3": ["mapmaker"], "-3.1 10.6 3.0": ["quadriplegia"], "-1.7 1.7 1.8": ["metabolizes"], "-0.6 0.7 10.7": ["terminaling"], "-2.7 1.7 7.4": ["embalm"], "6.1 16.6 17.2": ["knuckleballs"], "12.4 9.1 4.3": ["superimposes"], "-6.1 14.2 5.3": ["transmissibility"], "3.5 17.2 -0.1": ["burnable"], "4.8 -4.5 6.2": ["threeyear"], "3.7 11.8 9.7": ["drunkeness"], "17.8 8.6 19.6": ["sasquatch"], "10.7 21.0 8.8": ["dynamiting"], "-0.9 18.1 15.2": ["allicin"], "10.0 14.2 14.3": ["bating"], "19.3 27.9 17.9": ["archangel"], "-3.2 3.6 9.4": ["pleurisy"], "17.4 -2.9 21.3": ["macrame"], "-3.4 5.1 19.0": ["ikebana"], "4.1 4.9 12.2": ["siestas"], "3.6 -0.1 7.9": ["microcephaly"], "3.5 10.8 28.3": ["sedums"], "1.6 9.2 -3.6": ["banlieues"], "2.5 10.1 6.0": ["diasporic"], "12.3 15.9 18.6": ["henpecked"], "5.6 -3.7 3.2": ["progamme"], "4.7 -0.6 16.2": ["daniel"], "3.6 4.5 -1.1": ["reducers"], "3.9 2.2 12.9": ["snowless"], "4.0 11.5 15.4": ["homebodies"], "1.2 11.7 0.9": ["happed"], "11.2 5.5 34.4": ["gyoza"], "-1.0 19.3 -7.3": ["radicalising"], "3.1 -4.5 6.0": ["bankcards"], "0.9 -0.1 5.7": ["processability"], "-1.5 16.2 18.8": ["groundcovers"], "7.1 12.1 8.9": ["interferometry"], "3.5 7.0 9.1": ["destitutes"], "-3.2 -4.8 4.7": ["certif"], "7.3 6.9 4.9": ["sectorial"], "1.2 1.5 5.5": ["hydrotreater", "inclu"], "4.9 -1.4 10.9": ["notepaper"], "-6.0 5.7 6.4": ["indigence"], "3.7 7.7 24.9": ["voyaging"], "13.5 5.6 7.4": ["sunbaked"], "9.4 11.5 6.1": ["veritably"], "7.1 7.1 8.3": ["dendritic"], "-0.1 15.8 36.9": ["smallies"], "-2.8 5.2 2.4": ["cephalosporin"], "-0.5 6.0 19.5": ["herpetology"], "5.4 2.4 2.4": ["underwire"], "-1.3 2.6 3.5": ["anonymised"], "12.8 17.9 14.6": ["ineffectually"], "6.6 8.5 0.4": ["dramatising"], "6.0 9.2 11.1": ["fangirls"], "0.2 -2.7 5.2": ["bcfd"], "-6.6 8.1 3.6": ["defragment"], "0.4 4.0 2.3": ["multiroom"], "1.1 23.2 9.9": ["sentimentalist"], "5.2 6.6 5.1": ["unsettlingly"], "-1.3 0.8 8.8": ["latchkey"], "1.8 7.6 13.3": ["entrained"], "6.3 5.8 3.2": ["solenoids"], "6.4 12.0 6.4": ["randomize"], "2.4 13.5 12.2": ["habituation"], "7.4 1.5 5.8": ["carped"], "6.3 14.3 4.7": ["outlives"], "-2.6 4.1 1.2": ["isoflavone"], "5.3 23.3 14.8": ["mapmaking"], "7.6 10.0 5.9": ["schoolfriends"], "16.2 25.2 8.6": ["heartlessly"], "22.7 15.8 3.8": ["nanobots"], "27.5 11.7 0.4": ["misers"], "11.5 30.2 18.5": ["rune"], "-1.4 5.2 9.2": ["alternations"], "2.0 27.4 4.8": ["afghanistan"], "16.5 11.5 4.7": ["phantasmagorical"], "-1.7 11.8 6.8": ["misconfigured"], "5.4 15.1 10.4": ["sandboxing"], "18.2 7.7 7.5": ["clunked"], "7.7 10.6 3.8": ["unsought"], "-0.4 7.2 26.1": ["injera"], "14.2 9.5 10.6": ["ziggurat"], "15.9 4.1 5.6": ["metalworkers"], "-0.8 3.2 4.0": ["psychopharmacology"], "1.8 2.5 18.6": ["miscegenation"], "6.0 15.4 4.4": ["plainest"], "5.0 8.0 7.7": ["airheads"], "0.9 0.5 13.1": ["preppie"], "-7.7 12.8 13.6": ["subnets"], "-8.1 31.7 7.8": ["valorous"], "-4.2 -1.3 -4.7": ["availabe"], "16.9 3.1 2.1": ["advertizing"], "15.2 3.2 10.6": ["scaffolder"], "9.8 4.2 15.6": ["graham"], "1.8 4.1 7.8": ["multisectoral"], "11.9 -4.7 9.0": ["schlepped"], "4.9 13.7 1.2": ["desensitised"], "7.1 5.5 16.3": ["lotsa"], "8.2 7.0 10.9": ["prudishness"], "10.0 12.5 14.5": ["seism"], "6.3 5.4 3.1": ["inte"], "5.1 11.1 7.8": ["breakin"], "10.3 11.4 15.6": ["dawgs"], "2.7 9.5 12.0": ["ecologic"], "3.6 9.3 12.1": ["tipples"], "2.1 3.1 8.6": ["outdraw"], "21.3 11.6 11.0": ["entwine"], "5.6 26.7 10.0": ["inabilities"], "-2.3 -0.7 14.5": ["syabu"], "2.2 40.7 -2.3": ["mujaheddin"], "14.4 -1.3 3.7": ["warehouseman"], "5.1 10.5 38.6": ["barra"], "-1.8 -5.3 5.9": ["lates"], "10.9 6.0 4.9": ["neuromarketing"], "13.7 7.9 7.1": ["clearers"], "11.8 9.0 3.6": ["recharger"], "4.2 2.0 2.2": ["pps"], "15.3 6.9 16.5": ["kilted"], "1.9 3.2 29.8": ["orioles"], "-3.6 8.6 12.9": ["diaconate"], "9.3 17.2 1.4": ["streptococcus"], "-4.7 12.8 9.5": ["ductility"], "-8.2 -5.1 -2.6": ["clinicals"], "6.1 0.9 10.3": ["slopeside"], "-0.5 1.7 12.4": ["subsample"], "14.0 8.1 18.0": ["hickey"], "11.3 13.6 2.0": ["emanations"], "9.1 17.0 18.7": ["bather"], "13.1 3.1 2.7": ["flashmob"], "9.9 17.1 1.3": ["cybernetics"], "-0.9 1.1 12.6": ["flanged"], "-2.3 16.1 16.0": ["supermajorities"], "13.1 10.8 8.9": ["modder"], "-0.1 14.7 7.7": ["undistracted"], "-1.0 4.4 10.7": ["stagey"], "8.7 9.5 10.3": ["nerzog"], "10.7 15.5 5.7": ["manias"], "5.8 9.8 23.5": ["growlers"], "-1.3 -6.3 15.4": ["tun"], "-2.1 22.5 9.9": ["aught"], "7.0 5.7 7.9": ["lefthand"], "-1.7 1.2 8.4": ["oligomers"], "9.4 10.8 5.5": ["jetstream"], "3.1 4.8 1.2": ["sie"], "6.6 14.0 10.5": ["instants"], "10.4 11.3 9.2": ["etiquettes"], "-0.9 -1.8 14.8": ["swingy"], "10.3 3.4 23.9": ["biltong"], "3.8 11.0 2.9": ["counterarguments"], "15.9 7.9 30.7": ["redworms"], "10.7 4.3 11.1": ["salesroom"], "-5.1 1.0 -2.3": ["reversibility"], "-0.9 9.8 14.0": ["transgene"], "8.7 1.0 16.7": ["soyabeans"], "8.7 7.9 12.3": ["gary"], "7.4 5.7 33.3": ["bento"], "5.5 0.5 6.2": ["expanders"], "21.3 26.5 18.1": ["wraith"], "-2.2 5.8 17.8": ["tempranillo"], "8.2 14.6 13.0": ["polis"], "18.5 9.5 9.4": ["lethargically"], "3.1 1.3 6.4": ["teletext"], "3.7 1.9 4.4": ["posher"], "-3.8 5.6 20.7": ["manures"], "-2.9 8.2 8.1": ["highpoints"], "-0.9 5.4 17.6": ["colchicine"], "-4.4 2.2 7.9": ["bacteriology"], "0.7 6.1 9.8": ["andropause"], "8.3 4.7 19.6": ["streambeds"], "5.4 0.9 7.8": ["coffeeshops"], "3.3 18.6 3.5": ["unconcious"], "0.7 3.1 34.5": ["lychees"], "12.5 3.1 17.4": ["corncobs"], "-1.4 1.7 2.4": ["undercharged"], "9.9 8.2 -1.4": ["wallpapering"], "-0.5 -0.9 -2.4": ["incuding"], "-2.6 19.7 10.4": ["gaydar"], "9.2 9.4 8.5": ["colonnades"], "15.4 9.5 37.1": ["cattail"], "4.1 12.5 1.3": ["datelines"], "8.4 13.7 4.0": ["gamescom"], "-3.0 13.1 2.3": ["confirmable"], "2.8 2.7 6.3": ["palliatives"], "9.6 8.4 10.3": ["greedier"], "-1.1 -3.1 5.2": ["etalk"], "-2.1 11.2 13.0": ["liftboats"], "0.2 12.4 -1.4": ["arrogate"], "9.4 3.8 0.3": ["cleanness"], "10.8 6.6 6.4": ["pinholes"], "3.0 13.4 9.3": ["punctilious"], "1.2 8.1 4.7": ["legionella"], "4.9 10.6 14.0": ["houseboy"], "11.2 10.8 2.9": ["demutualize"], "4.1 14.2 8.3": ["oxidizes"], "8.9 15.3 -0.8": ["transmute"], "3.4 1.7 17.5": ["satins"], "13.4 5.9 16.9": ["yappy"], "16.2 14.3 16.8": ["sysadmin"], "12.1 16.8 7.8": ["dervishes"], "3.7 18.4 7.0": ["ablest"], "0.1 5.6 13.5": ["airbox"], "-1.5 6.0 4.6": ["circumcising"], "5.3 15.1 5.2": ["declaiming"], "-5.1 4.7 -0.4": ["dyskinesia"], "-3.0 5.3 0.6": ["herniated"], "22.0 -1.0 2.3": ["compnay"], "-5.8 13.7 24.5": ["winterkill"], "-4.5 3.0 4.5": ["gastroparesis"], "5.3 -1.8 15.3": ["chichi"], "-9.3 10.1 15.0": ["trailering"], "4.7 -0.5 20.6": ["gladiolus"], "2.0 4.6 15.1": ["byelaws"], "3.7 12.1 4.9": ["rousting"], "-8.7 0.6 8.1": ["ligatures"], "-0.0 2.9 5.3": ["draggy"], "4.5 11.4 9.8": ["plinths"], "5.1 43.3 -0.3": ["mujahidin"], "-4.0 10.5 8.8": ["gacaca"], "2.6 7.9 14.4": ["carisoprodol"], "4.4 11.6 26.5": ["poults"], "5.6 11.6 17.5": ["crossbody", "colluvium"], "-1.6 8.6 26.3": ["tailwater"], "0.1 10.6 6.7": ["antitumor"], "5.8 17.4 3.6": ["doubletalk"], "0.3 13.7 9.8": ["scrummager"], "0.4 11.1 5.3": ["voclosporin"], "15.9 9.1 11.7": ["backpedals"], "7.3 17.5 6.2": ["egomania"], "12.2 17.5 4.3": ["sledged"], "-7.9 6.1 2.5": ["levofloxacin"], "8.9 10.4 20.3": ["dehydrator"], "-2.2 3.4 11.4": ["peri"], "-1.0 13.4 11.8": ["contrives"], "10.8 3.3 3.2": ["microneedles"], "2.7 16.2 3.6": ["inquirer"], "-2.9 3.9 1.4": ["credentialled"], "16.2 2.9 4.5": ["stk"], "1.8 12.7 5.6": ["leftish"], "6.6 7.9 18.4": ["shrubby"], "-5.5 7.1 9.6": ["tumorigenesis"], "15.3 20.0 23.3": ["talon"], "4.1 24.0 1.1": ["sanctities"], "6.3 5.6 19.3": ["shorties"], "-0.1 -1.1 -2.8": ["publ"], "9.7 3.5 7.4": ["relighting"], "9.9 7.9 16.6": ["biomes"], "4.3 18.5 19.6": ["midcourse"], "4.5 8.2 2.0": ["harddrive"], "-4.7 10.4 9.2": ["dentin"], "1.4 6.4 4.9": ["iloperidone"], "17.8 5.8 11.4": ["whippersnappers"], "5.5 11.2 19.8": ["oryx"], "-2.1 4.2 9.4": ["gemologist"], "1.3 -1.3 13.5": ["restage"], "5.8 8.5 -4.1": ["localising"], "3.8 7.0 2.0": ["cleanrooms"], "-2.1 2.5 6.0": ["gmt"], "14.2 18.2 10.9": ["motherfucking"], "-7.5 -0.2 16.2": ["disenrollment"], "1.0 5.1 12.7": ["lowriders"], "-3.9 1.1 7.6": ["sinbin"], "1.6 4.7 0.6": ["casualwear"], "-2.7 17.3 2.2": ["touchpoint"], "12.2 8.1 6.7": ["sulphurous"], "6.3 7.3 4.1": ["flimsier"], "12.3 3.6 14.0": ["slimmers"], "2.3 3.6 12.8": ["bookbags"], "-6.0 11.4 5.2": ["commentors"], "-1.9 2.4 6.1": ["universalisation"], "13.1 11.5 1.5": ["gumshoes"], "-5.0 11.3 6.5": ["excitatory"], "4.3 8.9 11.8": ["calendula"], "11.9 8.9 13.7": ["skanks"], "4.8 3.1 5.6": ["straitened"], "7.6 -1.9 -0.5": ["exc"], "3.2 7.4 26.4": ["darters"], "4.0 -1.9 11.8": ["ferronickel"], "-2.6 0.4 8.6": ["platesetter"], "-0.1 5.8 13.8": ["ceramist"], "5.8 14.3 9.0": ["entangles"], "1.1 8.8 17.5": ["satiation"], "13.6 17.4 15.5": ["cuckold"], "5.8 16.4 4.8": ["resurrections"], "5.1 14.5 5.3": ["hedonists"], "0.3 28.3 -4.2": ["batallion"], "6.2 6.9 5.3": ["anchormen"], "2.7 13.3 2.4": ["lootings"], "-8.7 5.4 -2.3": ["aftertreatment"], "6.5 12.4 3.4": ["undistorted"], "7.4 14.9 3.1": ["footsie"], "16.0 27.6 11.5": ["pillboxes"], "6.6 2.3 12.6": ["toppy"], "1.1 10.5 -3.1": ["emoze"], "16.8 3.5 4.7": ["noughts"], "10.0 21.9 24.7": ["gingers"], "5.1 1.6 5.1": ["nannying"], "5.0 7.2 5.3": ["sem"], "-4.7 4.3 1.1": ["educationalist"], "12.2 -11.4 1.7": ["squarefoot"], "13.5 -0.5 7.7": ["redbrick"], "5.5 14.0 7.7": ["synoptic"], "6.2 3.2 7.2": ["mescaline"], "1.5 5.6 46.7": ["bangus"], "15.8 7.4 8.8": ["lassoing"], "1.3 8.2 7.1": ["weepie"], "1.6 6.5 11.9": ["zestful"], "18.9 11.0 24.1": ["herbivorous"], "3.7 8.1 32.7": ["harissa"], "-2.2 7.7 8.9": ["carrom"], "0.3 14.4 0.1": ["compartmentalised"], "10.2 -3.0 11.3": ["gussy"], "13.6 -0.1 6.2": ["preprocessing"], "4.8 4.2 0.0": ["conformable"], "6.8 33.8 21.0": ["powerups"], "9.6 8.4 8.2": ["bleated"], "10.6 7.0 3.4": ["uncommercial"], "10.1 7.7 10.7": ["blandest"], "-14.9 10.3 13.8": ["seasonals"], "-2.8 7.8 8.4": ["dissociative"], "5.4 23.7 2.6": ["blaspheme"], "3.6 6.5 8.6": ["atomizer"], "3.6 5.0 13.2": ["helmetless"], "1.8 9.3 9.2": ["toothaches"], "16.6 5.6 15.2": ["moola"], "16.7 19.4 16.1": ["swashbucklers"], "7.1 14.9 12.3": ["undergirding"], "13.4 10.6 12.5": ["handhold"], "11.8 7.5 37.7": ["succotash"], "-2.4 14.2 5.6": ["drylands"], "6.5 13.2 3.9": ["uncomplaining"], "-3.8 21.9 6.0": ["fellowmen"], "-4.7 4.6 11.9": ["tangi"], "14.1 1.3 4.4": ["flowcharts"], "0.1 5.4 -3.8": ["foreward"], "1.6 17.6 4.8": ["antagonizes"], "-5.6 5.4 13.3": ["paraquat"], "1.8 16.6 7.9": ["friable"], "6.5 17.9 -1.5": ["stupidities"], "-0.7 9.6 11.4": ["resected"], "-5.5 4.6 -0.5": ["unamended"], "13.4 4.3 33.8": ["bowlful"], "1.9 10.9 6.2": ["glamorizes"], "-8.7 10.2 8.6": ["cephalosporins"], "14.7 14.9 11.2": ["scythes"], "5.7 4.4 2.7": ["oui"], "-4.0 3.3 9.8": ["macular"], "8.4 11.1 9.4": ["strangulating"], "2.4 8.6 -0.1": ["idolises"], "19.7 17.2 10.3": ["ghostlike"], "-2.5 9.6 25.3": ["waterbodies"], "-0.6 18.0 9.2": ["reflectively"], "7.2 8.7 22.4": ["barfly"], "8.1 5.6 8.2": ["showjumper"], "-3.5 6.3 1.0": ["unlevered"], "-0.4 18.2 11.7": ["modus"], "7.4 8.2 6.1": ["venturesome"], "6.9 -1.1 6.1": ["flounced"], "-7.0 14.2 12.1": ["tossups"], "-6.1 3.1 -0.2": ["jeanswear"], "-3.6 6.1 9.3": ["soundcard"], "16.7 9.4 11.7": ["smudgy"], "11.2 10.6 25.7": ["partridges"], "-4.9 13.0 1.0": ["conjectural"], "16.1 12.8 8.2": ["abracadabra"], "-8.6 7.5 2.3": ["disestablished"], "11.3 12.2 -2.4": ["imbed"], "-11.3 18.3 10.2": ["reformism"], "4.3 12.8 11.2": ["ultrawideband"], "-0.8 5.8 8.1": ["vey"], "-8.0 11.8 5.8": ["picocells"], "2.8 -0.5 33.1": ["koa"], "-0.7 7.7 1.9": ["underfloor"], "5.3 0.8 11.6": ["granulation"], "-2.4 9.4 -1.6": ["consorted"], "0.1 3.1 16.5": ["biennials"], "10.4 6.5 -0.4": ["abutted"], "6.0 13.6 6.5": ["defendent"], "2.4 -1.6 9.9": ["larding"], "5.1 13.9 7.6": ["depressurized"], "5.2 1.4 14.4": ["toffees"], "-4.7 12.8 4.7": ["airspaces"], "-4.0 12.0 18.5": ["freeboard"], "-0.3 15.2 7.5": ["ultraliberal"], "8.4 9.8 12.0": ["crossways"], "4.1 8.4 10.5": ["kibitzing"], "10.8 -1.9 4.4": ["rubberstamped"], "-4.0 16.5 4.5": ["arrogated"], "-1.5 20.8 6.7": ["nonstate"], "2.3 2.2 8.8": ["caplets"], "8.0 3.6 16.8": ["potholders"], "8.6 -0.5 1.1": ["breakingviews"], "-6.9 4.8 0.5": ["embezzlements"], "7.0 12.5 2.8": ["drover"], "2.9 4.4 16.0": ["anderson"], "1.9 16.9 10.2": ["collectivization"], "-1.0 1.1 11.9": ["remounting"], "4.9 8.9 6.1": ["cladribine"], "-1.7 11.7 4.6": ["ammendment"], "9.6 9.1 18.6": ["fem"], "-5.6 2.8 18.6": ["skijoring"], "-2.4 9.2 29.1": ["durians"], "-4.3 9.0 6.1": ["concision"], "2.2 6.4 0.1": ["modu"], "16.1 3.3 8.1": ["colonnaded"], "6.6 1.5 -4.5": ["validator"], "5.4 16.7 9.8": ["intolerances"], "-1.3 16.8 7.1": ["demoralisation"], "7.9 8.0 5.6": ["washbasin"], "8.0 1.1 2.6": ["sniggered"], "5.1 10.3 2.5": ["unecessary"], "7.3 7.9 1.7": ["microkernel"], "7.6 -2.9 6.6": ["buh"], "7.8 12.3 35.5": ["stinkbait"], "0.2 -0.7 4.0": ["lumpsum"], "-2.5 12.9 3.3": ["blisteringly"], "12.0 11.3 11.1": ["whippersnapper"], "-4.2 10.7 -1.4": ["adduce"], "0.1 9.6 3.8": ["pretest"], "-4.3 2.4 0.5": ["misfiled"], "0.2 2.8 15.2": ["chiffons"], "0.4 16.0 -3.6": ["inculcates"], "0.6 19.1 11.8": ["smokejumpers"], "-2.3 5.5 37.5": ["chervil"], "8.7 18.5 8.1": ["transfiguration"], "11.3 15.9 12.1": ["fumigating"], "5.4 8.0 12.1": ["manors"], "1.7 34.2 11.4": ["unrighteous"], "-7.2 14.2 0.9": ["sightedness"], "7.2 6.9 7.2": ["squelches"], "15.3 8.0 21.8": ["jawbones"], "8.9 26.4 7.1": ["cultist"], "9.7 11.1 12.1": ["gobby"], "13.4 4.5 3.9": ["engadget"], "3.5 -3.5 11.7": ["vo"], "13.3 -4.1 7.6": ["vended"], "8.4 14.3 15.2": ["gesticulations"], "-2.1 5.8 4.5": ["untranslated"], "2.2 21.6 5.2": ["submissiveness"], "-1.4 5.8 16.6": ["lappers"], "-1.1 10.3 9.6": ["underpopulated"], "10.4 24.6 11.8": ["coldhearted"], "-1.8 8.5 -0.3": ["reprogrammable"], "-2.9 2.2 7.5": ["rehome"], "13.2 13.4 9.3": ["bugaboos"], "-0.5 8.5 15.0": ["strat"], "-6.8 8.3 0.3": ["madrassahs"], "10.7 -3.5 14.4": ["ure"], "10.4 6.0 15.9": ["slammin"], "-1.1 1.3 3.4": ["newstands"], "20.9 31.0 7.4": ["disruptor"], "6.8 18.0 9.0": ["hobgoblin"], "3.1 15.6 9.6": ["effector"], "-4.9 2.7 0.2": ["neurofeedback"], "2.6 29.3 6.8": ["agression"], "13.4 9.7 24.3": ["jibs"], "19.1 17.1 20.3": ["bioluminescent"], "-0.5 13.9 6.0": ["memorizes"], "-4.1 -1.5 9.5": ["homestays"], "5.6 8.7 3.3": ["fourty"], "9.6 7.5 6.4": ["exaggeratedly"], "-6.3 7.9 8.4": ["donee"], "3.7 0.7 2.4": ["ethyl"], "2.7 7.7 2.4": ["explorative"], "-10.8 8.5 13.7": ["overseeding"], "8.6 27.6 3.4": ["inexpressible"], "-6.7 3.9 10.9": ["holi"], "8.4 -3.9 6.0": ["midtier"], "2.7 15.8 20.0": ["sowings"], "7.1 15.8 -4.1": ["lionised"], "3.1 7.2 5.1": ["suprises"], "-3.7 -1.9 2.2": ["daugther"], "2.5 17.5 17.7": ["flyways"], "18.6 18.0 13.6": ["conquistador"], "10.5 7.6 7.8": ["damps"], "2.5 17.7 16.7": ["vileness"], "-0.9 8.8 10.6": ["afghanis"], "10.2 1.6 3.7": ["stabile"], "-4.1 3.2 6.6": ["bidis"], "4.6 7.0 15.0": ["beedi"], "4.1 12.5 11.5": ["tories"], "1.3 6.4 5.6": ["lordships"], "6.3 23.6 6.5": ["defiles"], "10.6 5.6 13.1": ["rollerblade"], "11.0 21.0 21.6": ["lifeforms"], "11.7 5.2 18.3": ["mildewed"], "-0.1 18.7 3.8": ["impoverishes"], "8.1 10.3 10.5": ["aspirins"], "2.4 2.3 6.9": ["detailers"], "7.6 3.5 8.3": ["litle"], "10.9 12.4 13.5": ["squirrely"], "5.4 0.1 8.8": ["outre"], "-7.0 3.0 6.3": ["bandobast"], "-4.8 14.6 12.8": ["centermen"], "-6.5 14.8 -1.9": ["contributer"], "9.2 10.3 -6.6": ["hackable"], "7.1 11.6 9.6": ["multispectral"], "6.8 10.6 11.7": ["glens"], "15.0 13.6 12.7": ["entombing"], "-0.1 10.5 6.3": ["unlettered"], "9.9 10.8 17.1": ["hussy"], "-2.8 5.0 1.8": ["decongesting"], "2.9 7.7 7.8": ["playdown"], "3.6 14.9 10.8": ["trancelike"], "5.3 26.8 7.9": ["denialists"], "5.2 6.9 -0.5": ["ghostwriters"], "-0.0 13.2 4.2": ["knowlege"], "3.9 19.4 -8.2": ["deify"], "2.6 2.3 25.7": ["lai"], "8.0 16.4 22.4": ["deeps"], "2.1 13.9 7.9": ["spiker"], "5.4 5.7 1.0": ["positioner"], "6.4 6.3 3.9": ["voestalpine"], "-15.1 2.7 -0.1": ["chrg"], "5.9 2.8 13.7": ["sei"], "3.8 4.4 25.7": ["sternwheeler"], "9.9 4.9 21.8": ["dianthus"], "0.8 1.5 9.5": ["checksum"], "4.5 4.2 3.5": ["foulmouthed"], "7.6 14.6 10.3": ["beanball"], "28.9 9.5 1.3": ["flogs"], "22.1 10.9 13.4": ["teflon"], "2.4 3.0 6.2": ["campervans"], "0.7 2.5 16.9": ["boutonniere"], "11.7 11.5 10.8": ["crossfield"], "7.4 11.0 22.7": ["poultice"], "-1.1 5.4 3.5": ["raunchiness"], "7.8 15.5 11.7": ["blankness"], "-8.3 6.3 -2.2": ["ascertains"], "-1.3 3.9 13.6": ["cadenzas"], "-3.0 -0.1 19.3": ["pallium"], "18.8 3.3 14.7": ["divi"], "8.4 7.5 -1.3": ["bayed"], "5.4 4.6 4.2": ["raciest"], "4.5 4.0 21.3": ["chalices"], "9.9 19.0 -0.0": ["blaspheming"], "-8.6 5.6 3.7": ["tapeout"], "10.0 3.8 17.0": ["peppermints"], "10.2 3.0 3.0": ["skimps", "cytostatics"], "0.3 12.7 13.4": ["headlocks"], "-8.9 6.7 3.6": ["entecavir"], "4.9 8.4 10.1": ["rockstars"], "9.6 8.1 1.6": ["nicknaming"], "12.6 4.9 11.8": ["highchairs"], "-10.8 9.3 15.2": ["waterings"], "9.9 15.2 16.0": ["gabachos"], "7.3 8.2 5.9": ["rosiest"], "2.0 16.3 4.2": ["poltical"], "-9.9 24.0 10.5": ["reraise"], "6.6 -1.8 1.5": ["multispecialty"], "9.5 13.8 15.5": ["millstones"], "13.4 12.2 30.5": ["frankfurter"], "8.0 9.2 12.1": ["playas"], "12.4 11.6 8.8": ["skillz"], "-0.3 13.4 6.2": ["trivially"], "3.5 11.5 11.4": ["overweighting"], "-5.8 9.2 6.5": ["acclimatizing"], "1.9 9.3 7.8": ["brigadiers"], "7.0 9.2 12.4": ["phospholipid"], "-4.1 4.7 6.0": ["unpriced"], "-1.4 0.3 7.2": ["baisa"], "2.3 5.0 -6.9": ["felicitates"], "1.1 4.7 8.3": ["bioavailable"], "4.1 16.2 -4.5": ["challange"], "9.9 13.8 11.4": ["chancer"], "12.1 8.0 21.9": ["vermillion"], "0.4 9.2 2.8": ["indentifying"], "6.0 0.3 21.1": ["bowties"], "2.4 6.4 9.2": ["ferrite"], "-9.3 5.4 9.9": ["intelecrm"], "7.3 6.0 6.1": ["thes", "charkhas"], "7.2 9.5 13.7": ["graybeard"], "0.8 12.2 0.2": ["readerships"], "1.7 10.9 2.2": ["obsessional"], "10.3 10.8 11.4": ["grandness"], "12.9 58.3 5.4": ["hostiles"], "7.4 4.1 46.1": ["fingerling"], "5.7 8.2 5.0": ["quenches"], "8.0 -1.2 7.0": ["glassworks"], "-0.5 14.0 9.5": ["flyhalves"], "8.6 4.7 15.9": ["meatiest"], "13.0 12.3 13.5": ["fermenters"], "8.7 5.6 19.8": ["blackcurrants"], "10.4 0.7 24.3": ["chia"], "14.8 6.9 9.5": ["poleaxed"], "-3.1 7.6 11.8": ["arguidos"], "-12.4 14.8 5.2": ["aeromedical"], "6.8 12.3 5.1": ["pranked"], "9.0 1.7 2.3": ["swoopy"], "-7.2 10.5 2.4": ["epistles"], "1.2 2.8 -3.0": ["mps"], "1.8 26.1 -1.9": ["propagandized"], "10.5 18.9 11.5": ["neologism"], "2.0 14.7 -3.7": ["independency"], "-1.2 4.8 49.6": ["clammers"], "3.6 8.3 -0.9": ["compressible"], "-2.2 13.6 18.6": ["mycobacteria"], "8.9 1.6 1.0": ["programe"], "7.3 6.7 10.2": ["ach"], "18.0 7.4 17.2": ["commods"], "9.4 1.3 6.2": ["infrastucture"], "3.9 -1.6 7.7": ["legwarmers"], "9.0 10.5 14.0": ["capsid"], "1.2 10.5 9.7": ["glute"], "18.2 11.4 18.1": ["clucks"], "10.1 16.5 22.9": ["shillelagh"], "6.0 20.4 5.8": ["quisling"], "16.5 7.7 6.8": ["muzak"], "0.9 14.9 17.1": ["bottomland"], "15.0 10.7 -3.1": ["multibrand"], "1.9 11.5 -1.9": ["permissibility"], "6.7 12.2 13.9": ["worktops"], "0.1 14.0 0.8": ["effortlessness"], "16.9 8.7 16.4": ["butterbeer"], "4.3 5.7 -3.9": ["glamorise"], "7.9 1.4 7.3": ["fel"], "13.7 15.6 15.7": ["philistines"], "21.7 7.7 35.9": ["guppy"], "7.6 11.8 4.8": ["tch"], "3.8 22.4 7.9": ["unworthiness"], "-6.2 11.0 3.8": ["cusec"], "6.9 12.1 -4.0": ["externalized"], "16.0 -0.1 11.3": ["ornately"], "-9.3 -4.7 6.2": ["guardianships"], "19.1 5.1 14.1": ["barkers"], "7.2 7.3 10.9": ["gdp"], "20.1 5.8 9.0": ["digerati"], "-5.8 8.0 2.4": ["fluticasone"], "8.6 8.7 27.1": ["carvery"], "3.7 12.0 11.7": ["erotically"], "6.8 0.6 8.7": ["bohemia"], "2.6 4.2 12.2": ["cruisin"], "-0.5 4.0 12.9": ["taonga"], "11.8 7.8 13.5": ["gaucho"], "7.4 1.8 0.1": ["deluging"], "4.6 9.9 0.4": ["episodically"], "3.1 14.8 3.2": ["monotonously"], "-0.6 5.1 2.4": ["desulphurization"], "-1.4 6.4 10.8": ["aliasing"], "2.3 -0.3 15.4": ["ky"], "0.3 16.9 19.8": ["huntin"], "-4.0 6.0 5.6": ["unimplemented"], "-2.3 8.2 8.3": ["pianissimo"], "-8.0 1.4 5.1": ["endoscopies"], "-7.5 -2.1 3.3": ["scholastics"], "3.2 24.6 4.8": ["manuever"], "6.8 16.3 3.4": ["unscarred"], "10.7 -0.2 15.4": ["crackin"], "2.5 6.7 6.1": ["waaaaay"], "14.8 3.3 14.7": ["bedpan"], "10.3 13.2 6.5": ["redundantly"], "-2.3 8.9 5.8": ["jaywalk"], "-6.6 19.5 10.6": ["unengaged"], "3.8 3.0 23.8": ["kang"], "3.7 5.9 20.3": ["unplanted"], "7.3 -1.8 0.7": ["unguaranteed"], "5.6 16.1 7.1": ["keylogging"], "15.0 1.1 6.9": ["superboard"], "5.7 5.9 18.6": ["mehndi"], "9.2 5.2 9.9": ["dulcet"], "3.3 -0.3 17.0": ["semisubmersibles"], "2.3 4.1 11.7": ["moodier"], "7.5 -0.3 9.5": ["monograms"], "-6.8 1.3 5.0": ["lamotrigine"], "-2.2 7.2 9.4": ["fenestration"], "0.7 15.8 4.4": ["seductiveness"], "3.8 10.2 9.0": ["drachma"], "1.8 2.8 12.6": ["pharmacare"], "12.3 29.1 19.8": ["swordsmen"], "5.4 6.2 25.8": ["moistness"], "11.6 11.1 13.2": ["nappers"], "10.0 -1.0 4.2": ["sobre"], "4.8 10.1 24.1": ["thrushes"], "1.7 2.9 14.7": ["carafes"], "-7.3 11.2 6.8": ["topotecan"], "1.1 9.3 8.8": ["interurban"], "-7.3 3.5 4.6": ["ratemaking"], "-4.9 5.2 14.0": ["feedstuffs"], "-0.8 25.5 6.6": ["victimizer"], "-1.0 6.2 12.7": ["voip"], "20.1 14.9 6.5": ["corporatized"], "-7.0 -1.2 -0.1": ["habilitation"], "-16.1 23.5 12.6": ["situationally"], "12.2 -2.3 7.4": ["ater"], "3.4 14.6 15.5": ["unvarying"], "-1.5 16.1 10.6": ["satcom"], "0.9 13.6 7.7": ["inartful"], "16.8 9.0 10.2": ["gawping"], "2.5 10.9 20.4": ["transect"], "20.8 20.2 9.1": ["motes"], "-7.6 12.7 7.7": ["inker"], "-12.7 -2.2 4.2": ["unpledged"], "9.4 12.7 11.2": ["ohh"], "4.8 6.8 7.6": ["staffroom"], "5.3 -1.6 14.9": ["shiatsu"], "14.9 10.9 -0.7": ["kowtowed"], "1.3 4.6 -3.7": ["ophthalmologic"], "-4.5 4.6 11.9": ["ema"], "10.0 -0.8 8.5": ["semitruck"], "12.3 13.4 17.5": ["bubba"], "9.0 23.1 12.2": ["depopulate"], "9.7 -0.8 5.3": ["mult"], "9.3 3.6 20.4": ["mezcal"], "-2.0 5.9 8.5": ["meningioma"], "11.6 3.0 8.0": ["eftpos"], "6.7 8.4 -1.7": ["rededicating"], "6.0 11.4 0.2": ["sightline"], "0.8 4.7 6.0": ["handfull"], "5.3 6.3 5.8": ["louvres"], "2.8 8.9 18.8": ["snorkeled"], "-10.1 0.9 15.7": ["streamflows"], "13.7 3.2 -4.7": ["deparment"], "8.7 2.0 16.5": ["ecru"], "7.6 4.0 22.5": ["perl"], "-1.5 13.4 6.6": ["examinee"], "8.5 6.1 8.6": ["accordian"], "8.6 9.5 47.9": ["bullhead"], "2.0 11.8 21.9": ["victuals"], "16.7 14.8 4.8": ["hyperdrive"], "-1.5 7.2 13.5": ["freediving"], "12.6 -1.8 9.7": ["whippets"], "2.2 3.3 -0.8": ["depreciations"], "3.7 7.2 6.4": ["sparseness"], "3.5 -4.6 -0.4": ["multicurrency"], "-3.6 -1.7 7.1": ["buccal"], "2.9 6.9 9.6": ["pontification"], "1.4 11.9 3.3": ["hade"], "4.0 8.8 1.3": ["northwestward"], "6.9 10.1 13.7": ["toolmakers"], "10.4 -1.1 10.1": ["kamagra"], "7.2 5.1 18.8": ["cardrooms"], "0.6 0.5 4.3": ["peats"], "5.3 3.4 5.1": ["guidewires"], "-7.9 7.2 10.3": ["placewinner"], "-3.1 6.3 14.2": ["gat"], "7.7 11.3 9.8": ["teevee"], "4.5 8.5 11.4": ["shrewish"], "14.8 2.8 16.5": ["jalopies"], "3.7 8.1 16.4": ["macadam"], "15.6 5.5 25.7": ["glutinous"], "14.5 6.1 10.3": ["burgeon"], "-2.4 3.4 13.1": ["calcitonin"], "6.1 18.0 9.7": ["hombre"], "-9.9 0.4 6.4": ["nearline"], "9.8 23.6 16.3": ["landmasses"], "4.5 -2.5 -3.6": ["fka"], "-3.1 15.5 30.1": ["waterfowlers"], "5.1 14.8 16.4": ["cleavers"], "7.7 11.7 10.6": ["emailers"], "7.6 15.8 6.8": ["staunching"], "4.9 19.2 3.9": ["interposed"], "6.9 9.4 23.8": ["dabblers"], "2.0 7.6 11.3": ["peridotite"], "8.0 -6.8 12.8": ["ahhing"], "0.0 2.7 0.4": ["metabolised"], "15.0 -3.4 11.5": ["jived"], "11.8 12.1 21.8": ["slicers"], "16.3 14.5 29.8": ["duckweed"], "-2.2 4.4 -7.2": ["electrophysiologists"], "8.7 15.5 2.9": ["dustproof"], "12.2 8.0 10.9": ["trannies"], "-1.4 7.9 0.2": ["msystems"], "-0.6 2.0 3.4": ["nonprofessionals"], "-0.4 4.7 21.0": ["browner"], "3.2 23.5 5.8": ["reveille"], "9.4 4.0 2.5": ["cou"], "7.3 10.3 32.5": ["shellcracker"], "1.6 3.0 3.3": ["roomate"], "8.1 5.2 3.1": ["crystallising"], "4.5 20.0 7.2": ["mindlessness"], "-8.9 6.3 15.6": ["cognacs"], "-2.9 9.9 2.1": ["supermax"], "11.6 5.7 10.3": ["paterfamilias"], "4.6 5.8 3.9": ["newshole"], "3.4 10.5 25.9": ["camembert"], "4.4 2.7 36.3": ["fontina"], "-1.9 17.0 5.7": ["floodways"], "8.8 7.4 11.9": ["regurgitates"], "23.1 19.0 11.8": ["hording"], "-0.0 30.8 12.5": ["unarmored"], "8.1 10.1 9.3": ["sould"], "3.7 -6.8 17.4": ["calfskin"], "3.8 3.8 -3.2": ["rst"], "3.9 16.7 10.1": ["slipperiness"], "20.3 23.3 22.7": ["beady"], "5.2 12.6 14.1": ["phylogeny"], "0.0 10.1 11.6": ["doored"], "9.8 10.7 7.1": ["industrialising"], "5.3 -2.6 9.3": ["phoneline"], "4.9 -2.3 9.4": ["fyi"], "1.3 9.5 7.3": ["restrictor"], "6.8 6.6 2.4": ["viably"], "6.4 16.5 9.2": ["odium"], "-8.5 16.7 4.1": ["unparliamentary"], "21.6 9.0 34.4": ["tapir"], "-0.9 1.4 -0.3": ["microplasmin"], "-1.9 -3.0 6.0": ["sonographic"], "22.9 2.4 5.4": ["dotcoms"], "12.8 14.2 7.4": ["numbskull"], "-0.3 4.6 6.1": ["glycosylation"], "6.0 3.9 -1.0": ["carcinogenicity"], "-4.6 5.7 14.2": ["flourmills"], "0.9 11.4 4.2": ["minimalists"], "1.1 9.6 5.7": ["platitudinous"], "3.1 5.9 14.1": ["sensuously"], "9.8 0.6 19.8": ["sawmilling"], "10.5 11.6 6.0": ["cowpoke"], "7.9 21.2 2.4": ["emancipatory"], "10.0 11.5 2.5": ["ruggedised"], "-8.4 -6.7 4.5": ["reinterviewed"], "11.9 6.8 -0.2": ["stakeholding"], "-3.2 -1.2 11.2": ["vanpools"], "-0.5 16.1 0.3": ["perspicacity"], "-9.1 -2.1 2.3": ["anticonvulsant"], "-7.3 8.2 4.4": ["sulfonylureas"], "7.5 18.3 1.9": ["tattletale"], "11.6 14.4 3.8": ["sleaziest"], "7.1 15.3 16.1": ["amy"], "0.5 3.1 0.1": ["kyphoplasty"], "0.6 10.8 24.6": ["coneflowers"], "7.7 10.1 10.5": ["sos"], "13.8 14.7 13.2": ["dislodges"], "15.8 20.8 8.1": ["outwits"], "7.2 13.5 6.1": ["actualy"], "2.3 12.5 8.5": ["besets"], "10.8 6.9 12.4": ["masque"], "14.4 11.0 15.7": ["circularity"], "7.4 9.1 18.5": ["fred"], "10.2 18.6 15.4": ["crims"], "6.3 12.4 25.3": ["sandbanks"], "13.7 -2.7 0.1": ["greenlights"], "17.9 8.2 9.3": ["munificent"], "1.1 38.3 6.0": ["kafir"], "-0.8 1.5 1.9": ["timetabling"], "-3.0 4.3 6.2": ["passives"], "12.5 0.7 6.2": ["thermoformed"], "8.8 9.3 15.5": ["horseshit"], "20.0 15.8 17.7": ["roosted"], "12.7 6.8 6.0": ["tetrahydrogestrinone"], "19.4 23.8 5.5": ["pulverising"], "3.3 9.4 48.2": ["bigeye"], "15.0 8.2 8.3": ["anonymize"], "4.1 15.2 44.1": ["longlines"], "-0.7 22.8 1.9": ["usurpations"], "-0.5 2.0 13.3": ["bris"], "6.6 2.9 9.1": ["seon", "filthier"], "-0.3 10.9 9.5": ["reparative"], "5.5 7.4 7.6": ["weft"], "3.4 21.3 1.9": ["percieved"], "8.8 10.2 10.0": ["dreamscapes"], "-5.2 1.3 8.5": ["furosemide"], "7.1 8.2 -1.2": ["schoolfriend"], "12.1 11.1 8.9": ["scrollable"], "9.7 6.3 3.2": ["translatable"], "-8.1 7.2 -1.9": ["upregulation"], "5.4 12.2 4.4": ["grossers"], "-1.4 8.3 12.1": ["hepcidin"], "-2.3 8.3 4.2": ["misallocated"], "0.8 17.4 17.5": ["votebank"], "3.7 25.4 3.3": ["treasonable"], "16.4 20.7 10.9": ["slimeball"], "18.0 4.3 22.8": ["clingfilm"], "-3.1 8.0 -0.5": ["superchargers"], "-2.5 0.4 9.6": ["novelas"], "7.0 7.3 9.2": ["krumping"], "1.2 21.9 -0.8": ["falseness"], "2.8 -7.6 2.3": ["fiveyear"], "0.4 2.4 15.2": ["piedmont"], "6.2 -6.5 8.0": ["pw"], "-6.3 15.1 1.3": ["epistolary"], "2.9 3.7 7.9": ["broadness"], "-3.3 13.2 9.2": ["superoxide"], "15.3 9.9 20.4": ["titties"], "16.3 -2.5 6.9": ["hocked"], "9.8 7.5 9.5": ["witheringly"], "1.9 10.0 8.1": ["summiting"], "2.4 3.2 7.1": ["geometrics"], "-2.5 6.9 10.3": ["churchy"], "11.9 16.5 9.0": ["prostrated"], "-5.9 -3.9 -7.9": ["ccording"], "2.3 1.5 3.0": ["midgame"], "1.9 14.6 10.1": ["imperturbable"], "-0.8 0.8 11.4": ["rehydrating"], "-1.7 15.8 9.6": ["unprejudiced"], "7.2 19.7 6.0": ["egotistic"], "14.5 5.6 3.6": ["seminude"], "14.0 3.9 22.1": ["decoratively"], "2.2 -0.7 11.4": ["fai"], "-1.0 14.0 18.0": ["pilotage"], "20.8 8.1 16.3": ["sharpie"], "4.2 3.3 18.1": ["fetlock"], "5.1 6.3 -1.1": ["consummately"], "-0.3 3.6 2.7": ["cystic"], "9.2 -8.1 6.4": ["wearables"], "1.1 2.2 1.2": ["kidswear"], "15.3 5.6 5.2": ["demountable"], "6.4 2.7 33.5": ["pangolins"], "-2.4 0.4 -1.3": ["telemonitoring"], "13.2 17.6 14.1": ["badware"], "9.1 9.3 7.1": ["rubberneckers"], "-5.8 1.6 7.1": ["walkaway"], "16.6 2.9 13.2": ["facings"], "12.5 3.4 8.5": ["podgy"], "21.1 16.8 6.8": ["grumpily"], "2.5 17.0 10.0": ["hierarchal"], "-2.0 5.1 6.4": ["kombi"], "3.1 9.9 14.6": ["surliness"], "8.7 0.6 14.7": ["nouvelle"], "7.5 9.3 -2.3": ["odysseys"], "5.8 6.3 4.6": ["commiserations"], "11.8 7.8 8.4": ["squalene"], "21.1 6.2 14.8": ["frothed"], "11.2 19.8 4.7": ["firey"], "8.2 11.2 27.6": ["pirogue"], "22.6 3.0 11.2": ["whirligig"], "2.8 2.5 10.6": ["rancho"], "8.1 -3.2 16.7": ["plasterers"], "9.0 5.9 8.0": ["autoclaves"], "5.6 22.9 2.2": ["dehumanizes"], "-8.6 2.0 10.1": ["hydrogeology"], "10.8 2.1 11.4": ["coupla"], "8.9 2.1 10.7": ["toyota"], "4.3 5.7 2.5": ["probs"], "13.2 4.5 2.4": ["messageboards"], "2.7 12.2 14.2": ["naw"], "8.6 19.9 11.6": ["troglodyte"], "-6.1 12.5 8.7": ["dispassion"], "2.7 6.2 6.6": ["pretextual"], "14.0 6.0 10.6": ["gatefold"], "1.5 13.8 8.3": ["pithily"], "6.2 8.4 0.2": ["airconditioners"], "0.0 15.2 3.6": ["recievers"], "-5.4 7.2 -1.6": ["interoperating"], "6.3 7.4 5.4": ["airfoil"], "8.3 5.1 13.3": ["tars"], "13.9 18.0 40.6": ["gobies"], "15.3 -2.6 2.4": ["dolling"], "4.4 18.7 2.2": ["sanctifying"], "14.3 23.6 10.8": ["beheads"], "-0.4 3.1 0.1": ["hosptial"], "-1.3 9.1 8.3": ["dissonances"], "11.7 1.9 19.5": ["malted"], "1.8 7.0 14.6": ["powhiri"], "7.4 15.4 5.6": ["incautious"], "10.4 11.5 6.9": ["broncos"], "10.6 13.2 28.8": ["cheftestants"], "5.9 6.3 13.7": ["hatter"], "11.6 -1.1 7.9": ["extruders"], "-0.7 6.5 15.7": ["daguerreotypes"], "5.1 8.2 1.9": ["producible"], "14.0 17.7 28.5": ["blowhole"], "9.0 14.8 13.0": ["tigerish"], "9.0 13.0 28.1": ["drawbridges"], "4.5 -0.1 3.6": ["sont"], "8.8 5.5 6.0": ["seamlessness"], "13.8 14.7 22.7": ["arborvitae"], "8.6 4.8 10.2": ["sandblast"], "7.1 -2.9 6.1": ["jazzes"], "-3.7 12.4 11.8": ["aimlessness"], "1.8 7.6 6.9": ["investible"], "2.8 3.5 14.3": ["shan"], "10.4 22.8 9.1": ["feebleness"], "5.3 7.5 7.5": ["nas"], "6.5 9.3 11.1": ["afore"], "6.9 6.1 9.3": ["minicab"], "9.3 12.3 0.1": ["pillorying"], "-12.3 1.7 -0.6": ["ascertainment"], "4.3 11.1 21.1": ["stamens"], "6.3 1.7 31.7": ["workboat"], "11.6 8.5 12.1": ["jillion"], "4.6 9.5 14.9": ["moistening"], "7.4 2.4 10.4": ["bouncier", "arian"], "13.8 8.5 13.4": ["barfing"], "5.7 28.2 8.7": ["biowarfare"], "14.9 10.9 11.4": ["splotchy"], "3.8 4.8 13.3": ["carless"], "-7.7 13.0 10.6": ["runningmate"], "4.4 24.2 5.4": ["arabs"], "-6.3 13.0 -1.9": ["immunomodulatory"], "-1.8 20.0 5.8": ["antigenic"], "9.6 2.9 33.2": ["pimento"], "12.5 7.1 21.0": ["smushed"], "13.6 14.8 16.1": ["fetcher"], "-0.4 16.8 8.4": ["sabermetric"], "4.6 4.1 12.9": ["softcore"], "3.8 17.3 6.5": ["unconfident"], "10.9 13.7 22.3": ["foxglove"], "14.6 -1.7 4.2": ["yesteday"], "-2.1 4.2 8.1": ["debuggers"], "-11.3 10.0 6.0": ["unresectable"], "8.0 1.3 16.5": ["cirque"], "18.6 11.7 18.8": ["spittoon"], "9.3 9.3 4.1": ["raunchiest"], "-1.1 15.7 4.6": ["untidiness"], "-5.4 4.8 9.6": ["ferritin"], "1.8 9.5 7.6": ["pilling"], "-1.5 8.3 11.6": ["chordal"], "-2.2 14.9 9.7": ["passphrase"], "-0.1 6.8 6.2": ["reverends"], "-1.3 9.0 9.6": ["confreres"], "-2.7 10.1 5.3": ["interlayer"], "17.1 18.7 4.6": ["proverbially"], "1.2 3.8 4.5": ["isomers"], "10.7 9.4 18.2": ["merrymakers"], "4.0 10.9 -1.0": ["goalball"], "-2.5 14.7 54.6": ["tautog"], "-4.4 4.5 7.3": ["adminstrative"], "10.8 1.5 2.9": ["skybridge"], "1.8 9.2 4.0": ["goalkick"], "8.1 2.9 9.8": ["componentized"], "18.0 21.8 14.7": ["goddam"], "9.5 16.7 10.3": ["deadens"], "-8.4 24.5 6.3": ["feloniously"], "5.8 14.1 4.8": ["costless"], "8.0 23.7 11.8": ["threequel"], "4.8 0.3 17.9": ["tearooms"], "8.1 10.9 4.5": ["lowing"], "-1.9 12.8 8.6": ["thirstier"], "6.1 9.5 12.0": ["arabesques"], "-1.7 5.7 8.6": ["partylist"], "4.0 18.1 3.5": ["craftier"], "13.8 5.3 14.0": ["palanquin"], "12.2 7.8 32.5": ["civet"], "15.5 16.9 5.8": ["heedlessly"], "8.2 2.2 21.4": ["myostatin"], "0.9 10.5 6.4": ["hyphenate"], "-5.9 -1.3 11.6": ["addendums"], "5.9 9.7 16.7": ["rawk"], "-7.2 3.8 2.9": ["kirpans"], "5.3 20.9 2.4": ["pretentiously"], "17.2 7.5 13.5": ["tipi"], "7.5 6.3 -0.5": ["crackup"], "2.8 3.8 2.7": ["oversharing"], "14.2 20.5 6.6": ["outmanoeuvre"], "2.3 11.4 17.2": ["ulcerated"], "1.7 3.6 5.6": ["bellboy"], "21.3 2.2 6.2": ["turbocharge"], "0.1 4.1 37.8": ["ackee"], "2.9 17.5 1.8": ["disfavour"], "-0.5 16.1 7.1": ["shallowly"], "-0.3 8.6 7.9": ["greeks"], "-4.2 7.4 0.5": ["prepetition"], "3.6 11.5 19.4": ["zinnia"], "-6.3 13.6 6.6": ["reactants"], "11.6 20.2 31.4": ["earwigs"], "3.8 4.0 4.1": ["medio"], "7.2 6.7 44.8": ["sawfish"], "1.8 1.4 45.6": ["pollack"], "5.1 7.7 8.6": ["ballin"], "-2.6 17.3 5.2": ["rasped"], "1.5 0.4 1.7": ["myalgia"], "9.4 10.3 11.5": ["delistings"], "-8.6 -1.9 8.3": ["anastomosis"], "12.5 15.3 10.4": ["sheepdogs"], "1.2 0.0 -0.5": ["copolymers"], "11.9 6.7 25.1": ["chows"], "8.9 13.2 15.0": ["wino"], "0.2 5.9 4.8": ["rss"], "1.2 1.9 9.0": ["rotan"], "9.3 14.9 8.7": ["blabber"], "-3.6 2.9 0.7": ["hematologists"], "-2.0 8.5 11.4": ["ragtop"], "-4.4 6.1 17.9": ["rebars"], "-0.6 0.5 -3.3": ["cnr"], "6.8 11.2 8.0": ["subdomain"], "6.1 -4.4 12.3": ["plaited"], "-8.7 6.8 4.0": ["injuried"], "-5.3 9.3 1.5": ["dacoities"], "-0.0 5.2 33.3": ["salumi"], "7.3 0.4 1.6": ["filmstar"], "6.8 5.5 12.6": ["paleoanthropologist"], "12.6 17.3 11.4": ["anthropomorphism"], "26.4 7.3 21.1": ["spiderweb"], "-3.9 14.1 5.3": ["interposition"], "6.9 3.5 7.5": ["regionalised"], "-6.5 -1.6 15.5": ["allografts"], "-1.3 3.3 9.4": ["rds"], "-11.4 5.9 3.0": ["arounders"], "8.0 7.6 18.9": ["posies"], "3.6 12.4 5.7": ["multijurisdictional"], "4.0 18.7 8.5": ["shotmaker"], "-1.5 13.4 10.1": ["downhillers"], "6.4 4.0 5.2": ["lex"], "12.4 13.1 10.1": ["veldt"], "3.1 -1.1 16.6": ["kara"], "10.0 8.5 17.5": ["oiler"], "7.8 13.5 -0.5": ["cryptographer"], "18.6 7.0 23.1": ["slushies"], "14.0 0.6 -3.0": ["pulsated"], "4.7 19.5 5.9": ["mistrusts"], "6.5 5.3 14.4": ["leo"], "7.2 5.7 16.2": ["twining"], "-1.3 7.7 12.0": ["suv"], "23.8 7.0 7.4": ["moonwalks"], "2.8 1.5 5.9": ["preforms"], "13.0 14.7 11.3": ["fundies"], "3.0 4.1 14.4": ["tracheal"], "-1.5 7.1 6.3": ["lexicographer"], "20.1 4.2 11.1": ["megaloads"], "4.9 6.7 -3.0": ["protectable"], "21.0 10.9 11.0": ["hayseed"], "3.0 5.2 12.3": ["mong"], "6.0 14.4 14.9": ["colorant"], "-0.1 -3.7 3.2": ["ations"], "1.6 4.9 11.6": ["nitride"], "2.6 15.0 10.6": ["conservativism"], "7.5 -1.7 17.5": ["qt"], "-1.2 12.9 2.3": ["noncooperation"], "9.6 15.5 7.9": ["unintuitive"], "4.0 5.2 17.6": ["dana"], "-10.5 5.7 11.5": ["albuminuria"], "3.8 23.0 27.3": ["copperheads"], "2.1 2.8 6.2": ["chicest"], "3.2 12.1 16.8": ["unseaworthy"], "8.7 7.2 4.8": ["polyrhythms"], "18.0 13.9 6.5": ["thunderclouds"], "6.7 6.7 10.9": ["tarty"], "11.8 2.5 17.7": ["quarterpipe"], "2.4 22.5 2.0": ["relativist"], "-1.3 -0.7 2.1": ["danseuse"], "-0.7 9.4 4.1": ["dilutions"], "-7.1 12.0 5.9": ["motorable"], "8.8 11.0 16.6": ["stupas"], "6.3 2.8 1.3": ["hardlines"], "8.9 11.4 9.1": ["michelle"], "10.1 3.4 33.4": ["chimichurri"], "7.5 22.0 10.0": ["redistributionist"], "8.7 12.3 7.0": ["imprudently"], "15.8 4.9 46.6": ["herrings"], "-0.5 5.2 3.4": ["foreperson"], "13.7 18.5 6.5": ["dullards"], "8.9 7.7 18.4": ["intertribal"], "19.0 23.3 24.0": ["amoebas"], "-10.2 0.7 1.5": ["teleseminars"], "5.5 14.0 4.3": ["supergrass"], "-0.9 21.8 30.6": ["downriggers"], "-8.9 11.3 -0.8": ["ijtihad"], "-9.4 6.4 0.3": ["placees"], "5.5 0.8 15.2": ["runabouts"], "18.6 13.0 4.6": ["ringfence"], "34.6 24.3 25.5": ["tentacled"], "1.0 10.3 9.2": ["lithotripsy"], "9.1 17.2 6.9": ["foolhardiness"], "-3.7 1.3 6.0": ["mmcfe"], "21.0 -0.7 10.4": ["bonny"], "1.8 -0.1 11.1": ["lobola"], "2.5 6.8 5.4": ["millirem"], "18.0 5.4 17.9": ["gumballs"], "-15.2 8.8 5.0": ["chemoradiation"], "-0.1 -5.2 7.4": ["liftings"], "6.7 -5.8 11.2": ["fantabulous"], "4.0 6.5 21.7": ["spaniels"], "-2.6 6.3 3.5": ["amperes"], "-1.1 11.2 4.9": ["linescore"], "2.2 12.3 7.5": ["causally"], "3.0 9.4 7.0": ["emaciation"], "0.1 3.0 2.2": ["liposomal"], "13.9 2.2 33.6": ["zucchinis"], "10.7 21.4 12.9": ["dumbness"], "-0.0 2.7 11.7": ["kiloliter"], "7.3 3.0 12.9": ["ejb"], "-2.4 3.1 3.7": ["congestions"], "28.7 22.1 22.2": ["velociraptor"], "12.9 11.0 10.2": ["prizefight"], "1.6 26.3 23.0": ["chiggers"], "4.1 2.3 0.3": ["lathicharged"], "9.7 16.1 6.0": ["unlighted"], "-3.3 0.2 5.3": ["receipted"], "-13.4 13.8 6.3": ["madrasahs"], "-13.2 14.6 7.0": ["halacha"], "1.2 31.3 10.2": ["deceivers"], "3.6 2.2 4.7": ["nonmanufacturing"], "1.4 11.8 11.7": ["paygo"], "3.9 4.0 2.3": ["cataplexy"], "7.7 -1.6 13.9": ["picayune"], "8.5 -3.8 19.2": ["bai"], "5.8 6.3 6.2": ["sensationalising"], "5.9 7.4 19.9": ["ocelots"], "-2.3 5.7 7.9": ["fluoridating"], "7.5 6.1 -0.5": ["durably"], "-8.6 7.4 5.7": ["neoplasia"], "10.9 -0.2 5.2": ["swaddle"], "13.8 7.7 6.0": ["changerooms"], "16.9 30.6 10.9": ["predations"], "8.1 8.1 17.1": ["smallcaps"], "12.7 16.3 1.0": ["scourged"], "-0.0 15.9 18.3": ["kendo"], "-6.4 12.7 16.0": ["retracements"], "-4.5 7.9 13.7": ["alloyed"], "3.5 7.9 4.9": ["sensorial"], "-0.5 2.7 8.1": ["addressability"], "10.2 -2.7 16.0": ["blu"], "-4.7 7.4 12.4": ["mineralizing"], "-1.1 -0.9 4.5": ["adjudicatory"], "7.9 3.8 5.0": ["drivin"], "6.6 5.8 7.7": ["lewis"], "12.0 17.1 22.7": ["wurst"], "-1.5 4.0 6.7": ["hyperthreading"], "13.9 24.3 17.3": ["propellor"], "9.8 7.9 17.4": ["totalizator"], "-0.2 1.4 6.4": ["rubidium"], "10.3 14.8 10.6": ["headbanger"], "4.3 7.5 10.2": ["plangent"], "2.4 2.6 0.5": ["keynoting"], "2.8 5.1 10.2": ["lysosomes"], "11.6 21.8 15.4": ["unthinkably"], "-6.7 14.9 -1.7": ["logistician"], "9.2 17.2 2.6": ["douchebaggery"], "2.6 10.0 2.0": ["uninfluenced"], "12.7 6.9 0.1": ["hight"], "5.5 8.9 11.5": ["pyeong"], "5.4 2.7 29.0": ["unpeeled"], "2.6 18.3 20.0": ["staysail"], "-3.8 18.1 3.3": ["eschatology"], "6.8 4.4 6.1": ["relicense"], "-8.3 -4.1 4.0": ["binti"], "-2.3 19.5 0.9": ["sepoy"], "3.6 12.1 3.0": ["actuate"], "-6.0 9.5 -1.7": ["reemphasize"], "-3.1 11.9 -1.8": ["positon"], "4.4 19.1 12.0": ["highwaymen"], "-3.5 0.5 1.2": ["litigates"], "19.6 18.2 7.3": ["accusingly"], "0.8 12.1 5.2": ["underhood"], "-0.1 9.5 0.7": ["neuroplasticity"], "10.6 15.4 2.1": ["preventers"], "11.6 15.3 11.4": ["lionesses"], "1.2 13.1 7.1": ["windings"], "9.5 9.0 14.7": ["gneiss"], "4.1 3.9 10.6": ["haiti"], "10.4 16.0 0.1": ["inducer"], "10.9 -7.4 3.9": ["puh"], "-0.0 3.2 -1.2": ["photometric"], "17.0 1.6 9.5": ["bouyant"], "7.1 11.2 15.4": ["wiseacre"], "5.5 14.1 2.7": ["sturdily"], "14.2 9.6 20.4": ["festively"], "-0.4 13.3 7.5": ["manto"], "4.7 18.7 3.5": ["psyching"], "-11.0 7.1 3.8": ["reinvestigated"], "5.8 -2.5 0.7": ["beyondblue"], "-4.6 0.6 -3.6": ["naseba"], "0.3 -1.3 4.1": ["playschool"], "12.8 5.9 20.4": ["hotplate"], "-11.0 5.2 3.1": ["notated"], "5.2 11.9 10.0": ["bintx"], "11.3 7.5 5.3": ["caboodle"], "17.9 -5.3 0.5": ["longrunning"], "-12.8 -0.9 6.5": ["amitriptyline"], "5.1 9.2 -1.0": ["stationmaster"], "13.0 11.8 14.2": ["skinflint"], "5.3 18.3 10.1": ["prevaricate"], "12.6 20.5 1.3": ["idiocies"], "-5.9 13.3 5.5": ["chlorinate"], "-12.5 17.6 2.7": ["rephrasing"], "0.2 4.9 2.8": ["wishlists"], "13.4 -0.7 12.5": ["roadbuilding"], "6.2 4.3 -1.3": ["nonexecutive"], "0.5 13.1 18.0": ["antivenom"], "-3.7 7.3 2.7": ["bball"], "-2.8 10.6 3.0": ["timesaver"], "-3.7 11.7 11.3": ["nonofficial"], "1.1 4.4 10.8": ["timecard"], "0.8 3.1 3.8": ["optimisations"], "11.2 2.9 9.3": ["cinches"], "9.4 1.6 8.8": ["sl"], "-0.4 7.1 1.3": ["choreographies"], "9.8 3.3 30.8": ["pud"], "0.8 6.5 11.6": ["balladeers"], "-0.2 -1.4 21.2": ["newbuilds"], "2.4 1.8 14.6": ["hypnotists"], "12.6 -1.3 20.1": ["marmoset"], "5.5 9.7 1.9": ["tyros"], "19.4 5.1 29.8": ["oceanarium"], "4.5 22.0 11.3": ["suppressors"], "3.4 2.2 2.2": ["radiograph"], "0.2 8.8 4.2": ["urticaria"], "2.6 9.1 5.1": ["rebasing"], "-2.7 4.8 6.6": ["prefabs"], "-1.5 6.9 6.6": ["lacquers"], "11.7 1.7 14.9": ["crinkling"], "4.1 6.6 17.3": ["granitic"], "15.0 1.0 6.5": ["overthe"], "10.8 9.4 9.3": ["cubbyholes"], "20.0 19.5 13.7": ["pixellated"], "16.9 19.5 6.5": ["prosaically"], "2.7 3.8 13.0": ["cerium"], "5.0 -2.3 4.8": ["coproduced"], "6.5 18.8 15.6": ["bacteriophages"], "10.1 12.7 2.2": ["bulldozes"], "8.2 8.0 3.4": ["unassumingly"], "8.5 1.5 14.0": ["skiffle"], "9.2 9.1 18.1": ["masqueraders"], "-5.9 9.6 24.5": ["muzzleloading"], "-11.1 1.4 -1.8": ["recitalist"], "-3.5 17.0 9.6": ["freemen"], "3.5 5.9 41.5": ["nigiri"], "10.1 14.9 4.6": ["revering"], "8.1 24.2 7.5": ["strawman"], "8.9 1.2 2.1": ["securitise"], "8.1 4.2 2.8": ["clairvoyants"], "3.9 0.5 26.8": ["pigmeat"], "4.5 10.8 21.9": ["nuthatches"], "13.8 12.0 17.8": ["shivery"], "13.8 -3.2 3.2": ["thirdquarter"], "9.0 12.8 5.8": ["furrowing"], "-11.6 4.3 4.6": ["trombonists"], "10.3 6.7 12.9": ["catacomb"], "0.4 5.7 4.0": ["auditability"], "1.5 5.1 3.5": ["electrochemistry"], "-3.2 9.2 5.3": ["nudism"], "-1.5 29.7 10.3": ["paladin"], "-1.5 9.0 9.7": ["imbibers"], "13.6 15.5 14.0": ["conjurer"], "14.9 7.2 5.2": ["supercool"], "10.5 14.4 14.3": ["duffed"], "0.3 4.7 12.4": ["muralists"], "4.9 16.5 38.7": ["cutlet"], "-2.6 7.5 21.5": ["anoxic"], "6.9 13.2 8.7": ["enervated"], "8.6 11.6 7.5": ["aesthetes"], "13.5 11.7 14.4": ["maquette"], "11.5 9.5 11.9": ["burgs"], "12.1 10.4 13.9": ["pushpins"], "5.9 -5.4 14.6": ["canalside"], "3.2 23.3 8.4": ["dangermen"], "10.3 11.7 17.3": ["highlanders"], "3.6 7.0 36.3": ["benthic"], "13.5 11.3 -4.5": ["telematic"], "0.5 7.9 2.5": ["setoff"], "7.1 16.7 5.2": ["immorally"], "13.1 1.6 21.4": ["tung"], "9.0 4.6 4.3": ["backrests"], "9.9 5.4 4.6": ["psychographics"], "2.5 15.2 3.6": ["tolerably"], "0.1 12.6 10.3": ["bushwalkers"], "13.6 1.9 13.9": ["gyration"], "4.3 12.8 2.4": ["eavesdrops"], "7.3 18.4 19.2": ["fieldsman"], "3.1 16.7 7.7": ["feinted"], "9.3 15.1 14.6": ["wonderfulness"], "19.2 26.1 5.8": ["beachheads"], "-1.6 10.6 2.7": ["neigbouring"], "-6.9 17.3 4.5": ["misremembered"], "11.2 10.7 6.5": ["nekkid"], "13.6 22.7 6.9": ["deathblow"], "6.7 4.7 9.0": ["zune"], "13.4 21.4 11.6": ["knaves"], "15.8 13.0 3.3": ["sneeringly"], "9.4 14.6 7.6": ["gravitationally"], "4.7 14.6 7.2": ["plasmonic"], "7.5 13.2 7.9": ["geostationary"], "-9.4 13.8 1.2": ["exculpate"], "-3.1 7.7 12.2": ["mek"], "13.0 5.2 9.3": ["dabbler"], "-10.3 23.3 6.6": ["reenlistment"], "2.6 15.3 15.4": ["cultivations"], "7.2 6.0 8.3": ["varnishing"], "6.7 -5.2 -0.3": ["ated"], "-11.3 1.7 9.3": ["postconviction"], "1.6 6.4 14.9": ["koto"], "-3.3 -3.7 0.8": ["dualisation"], "9.3 0.9 11.9": ["tatoo"], "-7.0 11.2 4.2": ["bcgi"], "4.5 8.2 5.1": ["thro"], "13.0 5.4 10.9": ["clockmaker"], "3.2 8.3 3.7": ["telecommuter"], "7.8 7.0 18.3": ["lath"], "-0.3 -0.2 5.1": ["carseat"], "22.0 9.6 7.0": ["glinted"], "6.9 4.0 19.9": ["apatite"], "15.4 8.1 9.2": ["geekery"], "8.6 13.8 8.3": ["cowhand"], "8.4 16.3 5.7": ["improvident"], "3.9 8.9 22.1": ["boxwoods"], "-0.3 4.8 8.6": ["sb"], "2.5 9.7 17.2": ["ultram"], "5.9 5.1 15.0": ["ranchera"], "-1.2 4.2 10.7": ["oxalate"], "6.9 3.4 7.9": ["lisinopril"], "-1.3 8.1 10.1": ["intrusives"], "-10.2 7.0 7.4": ["xerostomia"], "9.9 11.5 12.5": ["bushmen"], "9.3 -0.2 20.7": ["crispier"], "0.9 3.2 5.4": ["combustor"], "-3.8 7.2 7.3": ["housemaster"], "-6.6 6.4 9.1": ["ulna"], "5.0 -5.1 4.6": ["cochlear"], "-0.5 19.2 5.3": ["illuminator"], "14.7 8.4 6.2": ["brickworks"], "4.5 1.4 1.0": ["wc"], "3.4 7.2 3.0": ["bequeaths"], "9.0 8.6 11.8": ["okapi"], "-6.7 12.6 -1.5": ["inadvertence"], "-7.2 3.3 -2.0": ["empanel"], "4.7 7.9 8.3": ["valerian"], "-6.6 20.0 11.4": ["calculatedly"], "11.2 21.3 10.9": ["bludgeons"], "11.8 3.2 13.4": ["cheesier"], "9.3 6.4 4.9": ["tidies"], "-1.2 14.8 12.6": ["pedantry"], "4.9 10.8 5.3": ["overanalyzed"], "7.1 10.9 3.2": ["ake"], "-5.0 2.1 -0.8": ["backorders"], "9.6 30.2 12.2": ["armors"], "5.6 12.5 -1.7": ["assests"], "-1.9 4.7 -3.6": ["familiarizes"], "15.6 9.0 6.5": ["roustabout"], "2.9 -7.3 8.5": ["milkers"], "3.7 13.8 10.2": ["muffing"], "7.5 26.6 0.4": ["dehumanised"], "14.1 11.2 -4.2": ["miniaturizing"], "13.6 6.2 9.4": ["posterboard"], "-2.0 3.1 36.2": ["carbonara"], "5.7 15.0 27.9": ["coons"], "0.0 18.3 18.3": ["nightshade"], "25.3 38.9 20.9": ["marauder"], "8.8 7.4 1.0": ["tautly"], "-2.7 -0.2 1.9": ["eval"], "7.0 7.5 5.1": ["timezone"], "17.4 10.9 11.1": ["pendulums"], "12.2 3.2 27.5": ["coppery"], "5.3 15.3 8.7": ["nonentities"], "3.3 20.2 23.9": ["varroa"], "-5.4 7.9 0.3": ["executrix"], "1.8 5.5 -3.9": ["attenuates"], "7.2 -3.1 6.6": ["lumpiness"], "-3.7 11.1 27.8": ["dhal"], "19.8 5.4 7.5": ["fandango"], "2.4 11.8 13.5": ["antigun"], "9.5 11.6 12.1": ["platen"], "-3.9 7.9 5.8": ["dataflow"], "0.8 13.3 12.2": ["donot"], "6.7 -3.7 15.3": ["caftans"], "7.2 18.1 9.8": ["protectorates"], "-5.4 3.9 7.3": ["meterologist"], "28.2 10.5 15.8": ["megabank"], "-5.4 2.2 5.2": ["numismatics"], "5.1 10.3 10.2": ["indents"], "0.2 14.3 4.9": ["absolutly"], "1.8 6.8 3.2": ["telehandlers"], "6.1 -0.3 13.9": ["sieved"], "-0.9 9.7 25.3": ["daal"], "4.7 4.8 4.2": ["ight"], "8.7 15.3 2.3": ["deciphers"], "3.9 -4.5 18.0": ["corduroys"], "11.7 11.2 -2.7": ["fulminated"], "8.4 -2.6 20.8": ["hairnet"], "-5.9 6.9 8.6": ["consignees"], "16.3 14.1 6.3": ["obscurely"], "23.6 -1.4 10.2": ["festooning"], "7.7 1.4 2.4": ["upa"], "2.2 14.5 4.9": ["chocking"], "6.4 12.1 10.3": ["fadeaways"], "8.3 13.8 9.8": ["fearsomely"], "-1.2 1.7 -0.9": ["precedential"], "-3.4 6.7 2.9": ["cllr"], "2.3 8.3 15.3": ["problema"], "9.8 0.6 17.9": ["jasper"], "-1.4 -2.2 4.6": ["atheletes"], "-1.6 23.6 -0.9": ["ablate"], "0.5 3.9 5.3": ["unstudied"], "7.4 6.6 12.5": ["carabiner"], "-5.9 9.2 -4.2": ["electrophysiologist"], "-15.0 -2.7 8.1": ["testability"], "0.5 1.7 6.3": ["passthrough"], "3.8 7.4 3.7": ["counterprotest"], "5.9 19.8 3.2": ["prophesized"], "10.5 5.1 8.9": ["barcoded"], "6.5 1.6 20.2": ["adipose"], "-7.1 2.5 6.0": ["fundable"], "8.4 8.2 4.9": ["procurers"], "3.3 3.7 20.8": ["blintzes"], "1.9 7.2 0.9": ["dosimeters"], "9.7 2.3 5.3": ["wastebaskets"], "-2.0 0.8 7.8": ["seatpost"], "11.2 8.1 13.5": ["georgia"], "6.2 6.1 -1.2": ["hl"], "7.1 4.9 25.9": ["raku"], "4.8 9.3 0.3": ["uncelebrated"], "-1.8 -4.3 8.6": ["saidthe"], "7.7 9.5 7.9": ["unpenalized"], "20.0 4.4 10.3": ["singeing"], "-2.0 9.5 4.3": ["reteams"], "11.4 -0.8 11.3": ["nutrigenomics"], "11.2 4.5 9.2": ["turfing"], "15.1 5.2 15.9": ["plugger"], "1.0 1.1 16.8": ["shortboard"], "3.8 24.2 4.3": ["despicably"], "-2.4 4.2 -2.3": ["recoded"], "0.5 0.5 8.0": ["steelpan"], "4.4 3.1 -5.0": ["ndash"], "-2.3 -0.0 15.8": ["chignon"], "-1.2 10.2 1.9": ["phenomenology"], "2.8 11.2 3.2": ["extremly"], "17.5 8.4 12.5": ["unhooking"], "4.0 7.6 2.9": ["coronal"], "17.7 6.1 11.1": ["wildman"], "14.0 32.7 11.7": ["imperium"], "-3.4 6.2 10.2": ["banters"], "-3.6 15.3 10.5": ["trusties"], "1.6 16.7 5.5": ["fireline"], "5.3 1.7 2.5": ["sterilizers"], "4.5 14.0 16.0": ["loppers"], "-6.0 6.6 4.3": ["seders"], "15.7 19.3 7.3": ["crimefighter"], "11.3 10.8 13.0": ["squalling"], "22.9 2.5 19.8": ["toucans"], "3.9 -3.4 11.4": ["christenings"], "2.8 2.8 3.7": ["decouples"], "2.3 6.4 10.9": ["laddering"], "8.9 8.5 12.3": ["volleyballers"], "10.7 8.0 12.6": ["overindulgent"], "-1.1 14.1 13.2": ["fearfulness"], "19.1 26.0 11.6": ["neanderthal"], "11.1 13.3 1.9": ["nanoscopic"], "5.8 10.4 8.3": ["interoffice"], "9.5 17.2 8.4": ["samey"], "-1.4 7.4 10.1": ["frailer"], "8.9 3.3 18.4": ["overabundant"], "6.1 26.4 11.6": ["nationalisms"], "0.4 6.5 11.4": ["kyun"], "6.1 -1.2 -3.3": ["positioners"], "0.5 6.5 4.8": ["almirah"], "23.4 2.3 23.0": ["multihued"], "-1.4 6.3 6.6": ["tubulin"], "6.9 10.7 5.7": ["rotator"], "7.6 21.0 4.2": ["waterloo"], "4.7 5.3 11.7": ["ungrammatical"], "14.2 10.3 14.4": ["ponderously"], "20.3 21.6 7.3": ["sentience"], "-4.0 8.5 0.9": ["galvanic"], "11.1 -1.0 17.9": ["crinoline"], "7.6 13.7 6.4": ["unpleasantries"], "5.1 3.4 3.4": ["utah"], "16.1 3.6 7.5": ["trigged"], "11.2 5.5 11.3": ["barmaids"], "1.0 11.3 11.4": ["uninsulated"], "-2.9 6.9 9.0": ["overcrossing"], "2.2 -0.5 1.9": ["recommissioning"], "-0.8 8.2 13.7": ["birthstone"], "19.0 12.9 21.0": ["goober"], "1.2 6.7 -0.7": ["milieus"], "4.2 9.6 10.9": ["situps"], "9.9 9.8 8.7": ["subassembly"], "16.9 4.1 11.2": ["minicomputers"], "10.1 15.3 6.1": ["ecoterrorism"], "9.1 13.2 21.0": ["ecologies"], "7.6 13.4 18.4": ["olde"], "0.9 0.9 13.4": ["endosperm"], "-5.7 5.5 -0.3": ["justiciable"], "7.5 15.5 13.3": ["crucibles"], "14.6 8.2 9.2": ["detroit"], "0.7 1.4 11.4": ["chlorite"], "12.6 5.3 9.4": ["nosediving"], "4.1 -0.9 8.8": ["busk"], "11.6 7.1 27.3": ["pearling"], "-5.9 8.1 13.6": ["sarcopenia"], "8.3 13.0 11.6": ["microcosmic"], "3.6 22.1 13.8": ["goners"], "7.6 4.7 10.2": ["unmarred"], "10.8 8.5 8.8": ["cosily"], "11.7 5.4 9.8": ["gigaflops"], "-2.8 5.2 5.2": ["seroconversion"], "-6.7 -1.1 1.6": ["minuted"], "10.6 -3.3 12.3": ["vestment"], "-3.2 8.1 11.1": ["mycoplasma"], "-1.8 6.3 14.9": ["longboarders"], "9.7 2.8 11.1": ["nebbishy"], "3.1 8.4 2.4": ["rebased"], "-7.3 2.6 2.4": ["derating"], "-3.2 9.5 33.0": ["ragu"], "4.8 13.1 8.2": ["towable"], "13.5 5.5 9.6": ["sundowner"], "5.4 13.3 11.1": ["weaselly"], "-6.5 5.1 5.3": ["nondiscretionary"], "3.3 1.9 5.0": ["unitized"], "8.0 3.7 11.4": ["stele"], "1.4 10.5 24.8": ["stuffings"], "1.2 18.4 5.2": ["counterpunched"], "3.8 1.1 47.5": ["mahi"], "-5.8 8.5 6.6": ["theorising"], "-3.4 16.0 5.7": ["pradhan"], "2.2 18.7 22.2": ["fieldsmen"], "1.5 8.5 13.2": ["snarkiness"], "-11.4 4.5 18.0": ["pinots"], "4.6 15.6 11.7": ["resignedly"], "12.5 -1.1 10.5": ["fluoro"], "-9.8 5.9 13.5": ["marriageable"], "5.1 -9.3 12.7": ["floristry"], "5.9 3.3 15.5": ["snood"], "17.0 33.4 7.1": ["golem"], "-4.8 -2.8 -4.4": ["liasing"], "-1.6 5.9 5.9": ["drawee"], "8.4 21.2 10.1": ["melodramatically"], "8.9 11.2 13.0": ["joyriders"], "5.9 1.0 8.5": ["fenfluramine"], "9.6 5.7 7.9": ["straitjackets"], "14.1 17.1 8.1": ["cellcos"], "-4.3 12.4 10.2": ["parenthetically"], "14.4 13.3 15.2": ["superstructures"], "-8.8 0.1 -2.8": ["neonatologists"], "-1.3 -1.9 5.3": ["grandnephews"], "2.4 6.4 3.1": ["mouthwashes"], "0.7 13.5 -0.8": ["personnels"], "5.5 16.4 8.1": ["dehydrates"], "0.3 0.2 -0.4": ["visted"], "8.7 15.0 2.9": ["seatmates"], "1.2 7.3 9.5": ["chidren"], "-0.4 13.5 15.9": ["bantamweights"], "3.2 11.7 13.2": ["reimposing"], "6.6 14.1 15.3": ["pedant"], "-1.6 5.6 21.2": ["doughs", "silts"], "12.8 10.0 15.8": ["ballyard"], "2.0 6.8 -0.6": ["revivalism"], "-0.9 1.0 5.0": ["cfd"], "3.7 17.5 11.7": ["waterholes"], "15.9 9.0 9.7": ["convolutions"], "-10.1 2.5 4.3": ["hyperphosphatemia"], "9.5 16.1 11.8": ["iframe"], "7.2 5.8 6.3": ["blazingly"], "0.2 20.0 4.9": ["mottoes"], "7.1 1.8 4.0": ["housecoat"], "-10.0 5.4 3.7": ["mcfd"], "1.0 -0.5 6.1": ["groundbreakings"], "16.3 14.8 11.4": ["wedgies", "gasbags"], "10.7 7.2 4.8": ["uncoupling"], "-5.4 11.5 9.4": ["cueists"], "3.5 7.5 7.5": ["jpegs"], "9.3 22.4 12.3": ["antiheroes"], "11.7 4.5 12.6": ["fortunetelling"], "-0.6 12.1 5.6": ["sanest"], "19.8 7.5 13.1": ["cheep"], "7.9 30.3 5.7": ["squaddie"], "4.9 22.7 2.1": ["laconically"], "10.5 11.0 11.9": ["plenitude"], "2.7 3.1 17.7": ["ery"], "3.4 -3.0 5.9": ["mea"], "4.4 7.6 7.6": ["fetu"], "1.0 2.5 6.4": ["ters"], "-4.3 0.9 5.5": ["belinostat"], "3.7 29.9 9.0": ["blasphemers"], "5.0 -2.5 5.4": ["lipgloss"], "8.6 4.8 10.8": ["barmen"], "-0.7 11.3 3.9": ["remapped"], "25.0 0.1 8.8": ["plasticized"], "-2.2 3.7 3.2": ["ceramide"], "1.7 20.7 3.8": ["unlawfulness"], "9.9 11.0 19.4": ["honeycombs"], "11.8 1.0 7.1": ["dales"], "-7.8 4.3 4.8": ["authenticators"], "-1.2 11.1 12.3": ["startline"], "2.4 6.0 17.4": ["adderall"], "4.6 -0.4 4.3": ["reappoints"], "7.1 2.1 19.3": ["antiqued"], "-8.8 6.8 2.5": ["frisks"], "1.8 6.8 27.6": ["codling"], "-0.9 1.6 16.2": ["amalgams"], "27.8 10.1 32.2": ["cephalopod"], "7.8 7.0 3.8": ["overhype"], "-5.3 -2.1 2.0": ["fundraises"], "-6.1 -3.1 -6.9": ["accomodated"], "6.1 1.9 8.6": ["femurs"], "0.0 2.3 7.2": ["jb"], "5.5 1.3 11.7": ["sesh"], "4.2 12.0 11.2": ["hashmarks"], "14.5 10.7 20.5": ["buttercups"], "1.9 11.3 18.9": ["spermatozoa"], "-12.3 10.3 18.5": ["rieslings"], "16.2 21.6 24.9": ["mandibles"], "-4.6 0.7 5.2": ["calcitriol"], "8.2 2.2 24.1": ["shanghai"], "-2.0 14.6 1.8": ["immodesty"], "8.2 5.7 12.4": ["zonked"], "15.1 9.5 13.8": ["alights"], "3.3 15.6 16.6": ["cosplayers", "zoysiagrass"], "12.9 1.5 3.6": ["racheted"], "8.9 14.6 9.1": ["altruistically"], "2.6 -6.0 6.1": ["overnighted"], "11.0 9.0 11.7": ["bittorrent"], "4.3 8.0 16.9": ["posy"], "12.9 13.8 10.1": ["zings"], "5.0 12.0 8.6": ["unconcealed"], "6.5 8.6 32.8": ["kakapo"], "7.1 11.4 13.5": ["lites"], "9.8 13.9 -5.3": ["immunizes"], "-11.1 5.0 6.6": ["scholastically"], "11.0 18.1 14.5": ["firebugs"], "3.2 9.2 8.0": ["ironwoman"], "2.8 5.7 0.3": ["tomake"], "-7.1 8.1 0.5": ["mileages"], "-3.8 5.6 9.1": ["marathoning"], "7.5 -4.8 5.4": ["squired"], "0.9 1.2 15.8": ["oxfords"], "7.8 11.1 6.0": ["prematch"], "5.2 21.6 4.4": ["misogynists"], "13.1 14.2 8.1": ["commoditize"], "5.1 9.0 19.1": ["hatchings"], "2.8 16.8 15.2": ["bucketing"], "12.4 9.1 6.0": ["philes"], "-1.6 7.1 9.0": ["bursa"], "8.6 5.1 16.3": ["refloating"], "12.1 4.3 26.8": ["choco"], "-7.1 5.8 7.3": ["chamberlain"], "-2.2 2.8 1.9": ["suffragist"], "6.8 3.4 21.7": ["aperitifs"], "4.3 1.9 9.5": ["daytrip"], "-2.7 14.6 14.2": ["kaise"], "12.9 15.2 13.9": ["seeder"], "3.3 12.6 11.2": ["solitudes"], "13.0 1.4 9.3": ["chockfull"], "16.9 8.9 21.0": ["plumed"], "3.3 -0.4 2.5": ["tiding"], "12.4 -5.2 0.3": ["facilty"], "-3.4 6.5 7.7": ["sellside"], "9.0 8.3 16.5": ["microsatellites"], "-4.9 7.1 9.8": ["hemochromatosis"], "15.2 20.2 12.9": ["antis"], "13.5 -0.8 15.7": ["fra"], "-3.1 4.2 6.3": ["hedonic"], "-5.7 5.9 2.0": ["coterminous"], "14.3 31.7 20.7": ["katana"], "1.1 1.9 11.5": ["cryptosporidiosis"], "4.0 -2.2 7.3": ["seok"], "13.9 12.9 5.2": ["swedish"], "6.1 10.0 -1.3": ["retorting"], "8.3 6.9 5.8": ["ould"], "-12.7 5.2 5.9": ["bronchodilators"], "6.7 18.9 17.0": ["namecalling"], "-2.7 20.7 5.2": ["conciliate"], "13.1 11.9 8.9": ["handsomest"], "12.5 14.0 16.0": ["britain"], "0.1 7.0 6.7": ["blowjobs"], "17.0 7.8 10.7": ["jigsaws"], "16.3 22.4 21.1": ["blockhead"], "-0.7 6.4 8.0": ["acetylation"], "4.2 16.1 12.0": ["fruitfulness"], "1.0 4.4 11.7": ["nanopores"], "7.7 -2.9 5.0": ["gah"], "-2.4 45.6 0.1": ["mujahid"], "7.6 3.6 0.1": ["zijn"], "-6.7 4.3 8.7": ["workplan"], "-2.5 9.4 12.9": ["diagnostician"], "1.4 -10.9 0.5": ["apperances"], "1.0 9.8 7.7": ["materialisation"], "-2.0 3.0 12.8": ["madrigal"], "-5.2 6.8 6.4": ["reoccurred"], "7.8 10.1 12.9": ["yipping"], "-1.9 5.9 3.2": ["explicate"], "2.4 9.3 9.7": ["butcheries"], "0.0 1.5 1.9": ["nce"], "2.8 7.2 4.2": ["invigoration"], "16.5 5.2 18.9": ["breakdancers"], "20.2 4.6 21.4": ["pebbled"], "0.1 5.3 4.1": ["narrowbody"], "15.7 4.5 14.1": ["waifish"], "11.8 2.5 15.7": ["stalagmite"], "1.5 4.9 10.8": ["gigatonnes"], "10.4 8.4 18.1": ["tipplers"], "2.1 20.7 7.3": ["counterpunches"], "0.8 12.0 6.3": ["noes"], "10.7 9.8 9.2": ["unsaleable"], "16.8 -6.1 11.1": ["perkier"], "4.7 6.9 9.7": ["emulations"], "8.4 12.8 5.4": ["fetishized"], "1.2 8.4 26.3": ["savories"], "11.4 1.7 18.2": ["bobbin"], "8.7 9.2 15.3": ["bullhooks"], "-4.5 7.4 -0.5": ["inquirers"], "11.7 10.3 4.3": ["schoolrooms"], "-6.7 6.6 5.1": ["hemostatic"], "-1.2 -1.8 10.5": ["relicensed"], "0.6 13.1 8.4": ["matmen"], "15.1 13.1 2.8": ["beseiged"], "6.8 2.1 8.7": ["rr"], "8.9 15.6 9.8": ["perfunctorily"], "11.3 4.9 28.9": ["delectables"], "4.2 7.8 8.3": ["excessiveness"], "-0.1 16.0 7.4": ["deduces"], "11.9 0.1 15.1": ["flumes"], "-0.6 0.8 8.1": ["retigabine"], "1.7 10.8 12.0": ["gulley"], "7.7 8.0 2.7": ["goaler"], "9.6 6.6 5.1": ["lockboxes"], "1.5 8.8 2.7": ["neice"], "-4.7 -5.5 6.2": ["dressmakers"], "6.0 9.6 12.6": ["nucleosomes"], "-6.7 -3.9 3.3": ["chaperons"], "8.4 4.8 14.5": ["midmonth"], "5.7 6.5 3.3": ["phosphodiesterase"], "-7.7 2.6 14.0": ["polyunsaturated"], "10.3 3.8 6.2": ["sto"], "-0.6 8.7 20.3": ["dentition"], "6.2 12.4 12.5": ["millworker"], "-3.3 3.6 -5.8": ["transcriptionists"], "5.6 16.1 9.9": ["upshift"], "-3.1 9.0 2.1": ["overspeeding"], "-1.6 1.3 7.8": ["reinstitution"], "24.2 10.5 19.1": ["millipede"], "13.7 6.5 12.9": ["neigh"], "5.7 16.1 8.9": ["midsentence"], "2.3 5.9 10.7": ["handcycle"], "3.6 2.5 7.5": ["suncream", "mig"], "3.6 -0.6 7.1": ["backgrounders"], "5.0 22.4 8.9": ["hatemongers"], "19.5 18.8 15.0": ["catlike"], "6.2 3.6 12.1": ["througout"], "1.0 9.0 9.3": ["reforested"], "3.7 6.6 10.4": ["brasses"], "19.1 9.4 2.5": ["gasworks"], "6.8 10.2 13.6": ["photoreceptor"], "3.9 3.6 -0.9": ["purveyed"], "13.0 4.6 7.5": ["ibm"], "11.4 3.6 32.3": ["pates"], "-10.6 4.2 2.8": ["rehospitalization"], "-0.4 14.0 6.3": ["madarsas"], "-12.2 5.4 5.5": ["prefrontal"], "4.7 8.6 12.8": ["debarking"], "-1.3 0.3 7.8": ["legwear"], "9.2 1.8 14.0": ["basque"], "9.8 6.7 7.0": ["ejaculating"], "9.1 16.4 11.2": ["ebola"], "-2.8 8.7 5.3": ["outstay"], "14.2 14.3 6.0": ["rottenness"], "14.7 12.0 14.7": ["pantomiming"], "9.8 9.4 14.7": ["bagmen"], "4.7 7.6 7.6": ["sintered"], "10.3 18.6 2.0": ["fenceline"], "7.2 9.2 8.0": ["stormier"], "5.1 18.7 9.1": ["unpowered"], "10.1 17.1 15.8": ["statelet"], "0.2 17.4 4.3": ["affectively"], "4.6 15.4 6.6": ["excoriation"], "10.5 7.6 -2.4": ["sucessfully"], "10.1 10.8 20.7": ["powerball"], "4.5 0.5 15.3": ["anomalously"], "5.4 21.9 5.0": ["snorer"], "-2.2 16.9 11.9": ["stomata"], "-4.8 13.8 8.2": ["disestablishment"], "20.0 13.6 38.9": ["jellied"], "2.9 0.7 5.0": ["relegations"], "10.9 -1.2 13.2": ["flounces"], "8.9 -7.0 12.2": ["gourdes"], "10.8 9.4 11.0": ["sideway"], "9.1 4.7 6.5": ["foundling"], "-1.1 8.5 4.9": ["stimulations"], "-3.8 2.9 5.1": ["jilbab", "privilige"], "13.8 4.6 6.6": ["bedpans"], "-3.9 6.7 0.3": ["verifiers"], "-2.2 10.3 12.3": ["annuitant"], "4.6 10.3 9.9": ["sightholders"], "-1.3 5.1 -1.9": ["practicability"], "7.8 25.8 18.9": ["maims"], "-5.1 -3.3 0.3": ["bylined"], "16.6 11.0 16.7": ["spivs"], "9.7 9.5 -2.1": ["idolising", "logotypes"], "-1.5 -4.2 -3.6": ["validators"], "3.8 2.3 15.0": ["coverlet"], "0.5 17.5 1.7": ["preborn"], "-5.4 11.6 7.8": ["itemization"], "4.6 6.0 7.9": ["sortation"], "15.6 5.0 13.4": ["winos"], "8.3 6.0 3.2": ["tieless"], "-2.4 11.6 3.5": ["federating"], "15.6 8.8 12.7": ["stubbly"], "-3.6 12.4 15.2": ["colorblindness"], "8.7 6.4 7.7": ["ritziest"], "1.8 9.5 7.5": ["experimentalist"], "8.7 0.6 9.3": ["tankful"], "-0.7 1.1 5.9": ["chaffing"], "13.6 14.8 15.7": ["undercarriages"], "-2.4 8.6 12.9": ["salar"], "7.6 10.4 3.2": ["basecamp"], "1.6 10.1 5.7": ["searingly"], "5.9 4.9 11.0": ["overfilling"], "-7.6 12.3 4.4": ["debriefs"], "8.5 9.6 16.9": ["mastic"], "-5.1 16.2 4.3": ["callsign"], "2.6 13.1 6.8": ["pianistic"], "6.2 5.6 -0.9": ["einen"], "-1.7 -0.7 21.0": ["bridgework"], "8.0 4.0 2.2": ["gazumped"], "7.1 9.1 13.7": ["overcomplicated", "amputed"], "-0.7 9.0 3.8": ["lasix"], "17.0 6.3 11.9": ["undulates"], "1.7 16.4 1.0": ["radiative"], "-5.7 -7.5 7.9": ["cytogenetics"], "9.7 8.9 17.1": ["barflies"], "5.6 1.6 8.1": ["bellhops"], "7.8 10.9 15.2": ["crapware"], "4.1 5.7 2.5": ["noncontrolling"], "15.5 9.8 39.6": ["courgette"], "6.7 6.9 16.8": ["bea"], "1.6 4.4 6.7": ["bday"], "-4.6 7.7 4.6": ["talactoferrin"], "6.7 6.2 3.7": ["newsphoto"], "-4.9 18.8 8.0": ["groupism"], "4.1 2.8 36.0": ["lechon"], "-0.3 19.4 7.7": ["stovepipes"], "4.6 8.7 2.0": ["betweeen"], "10.6 6.2 3.8": ["pulsations"], "10.4 -1.1 7.7": ["houston"], "11.6 6.4 15.2": ["nonviable"], "5.5 3.3 8.4": ["ln"], "9.4 10.3 0.2": ["awes"], "-0.1 1.0 5.5": ["underspent"], "7.7 9.6 0.4": ["evo"], "-2.6 20.3 11.1": ["irresolute"], "3.2 8.3 9.8": ["unresolvable"], "2.5 17.6 14.0": ["organelle"], "10.8 4.1 7.1": ["unicycling"], "-7.1 11.2 -0.5": ["milage"], "14.7 8.4 24.0": ["coreopsis"], "-2.9 0.7 12.7": ["areawide"], "-8.8 12.8 3.3": ["deployers"], "14.9 9.2 4.9": ["rectilinear"], "1.5 0.2 7.6": ["sidetracks"], "4.2 2.7 17.9": ["unclipped"], "9.6 0.3 8.0": ["repro"], "0.3 8.8 27.3": ["vindaloo"], "1.0 0.1 -1.0": ["nebulizers"], "-5.4 4.3 4.6": ["outpolling"], "-1.9 16.4 17.4": ["roamers"], "0.4 5.4 11.6": ["bornite"], "0.5 5.9 10.8": ["noncancerous"], "-2.9 5.7 0.5": ["thiazolidinedione"], "-3.6 12.4 17.2": ["botrytis"], "12.1 11.2 19.9": ["taxonomists"], "-4.3 3.0 3.9": ["malabsorption"], "1.7 8.9 2.2": ["ducted"], "11.5 8.0 -4.7": ["bedrocks"], "-7.5 -1.2 8.6": ["chlorhexidine"], "5.0 5.1 17.6": ["earaches"], "1.3 4.3 52.4": ["scallopers"], "7.2 5.0 7.4": ["sanitizes"], "-7.7 0.2 5.8": ["dressbarn"], "6.1 4.6 15.7": ["bronc"], "4.8 24.4 10.4": ["corruptive"], "4.0 3.9 4.1": ["incorporators"], "-7.7 15.0 14.6": ["pyrethroids"], "-10.6 8.6 10.1": ["endnotes"], "-2.7 0.2 10.1": ["monaural"], "-7.4 5.0 6.3": ["reval"], "-2.6 10.0 -8.6": ["disqualifier"], "11.8 10.7 16.3": ["pampas"], "5.6 8.6 8.0": ["toddlerhood"], "-5.2 7.1 16.0": ["lemonades"], "8.3 4.4 3.3": ["beddings"], "4.3 12.3 0.8": ["parivar"], "4.6 8.3 11.1": ["uhhh"], "-6.4 9.6 3.5": ["overvoltage"], "-0.7 -3.7 7.0": ["condonation"], "-4.2 5.3 7.6": ["resorption"], "-2.0 9.0 13.3": ["jocularity"], "2.0 14.9 4.1": ["unreasonableness"], "13.9 6.3 16.9": ["tankard"], "-3.0 13.2 12.8": ["seasiders"], "8.8 13.0 11.5": ["arrowing"], "6.5 5.0 44.6": ["toro"], "18.6 8.2 7.6": ["musclebound"], "-1.4 7.2 12.2": ["filesystems"], "-1.0 8.0 1.4": ["coronial"], "16.9 13.8 13.4": ["silverback"], "17.2 5.0 -0.3": ["mouses"], "-3.4 12.8 10.2": ["stationhouse"], "-3.7 5.1 0.8": ["wouldbe"], "-4.3 3.7 -7.8": ["choosen"], "8.2 8.3 -4.0": ["photomontage"], "13.8 7.1 0.4": ["nanosensors"], "7.5 0.3 35.3": ["spareribs"], "15.1 14.8 9.3": ["electromagnets"], "-9.4 2.6 9.4": ["unappropriated"], "8.5 18.0 3.6": ["wellsprings"], "8.9 5.6 12.2": ["ees"], "9.4 9.8 7.9": ["insensitively"], "-1.3 5.6 4.5": ["desireable"], "2.0 24.2 0.2": ["disempower"], "-9.4 -2.9 -2.8": ["countersigned"], "-3.6 12.1 7.5": ["overact"], "17.9 13.1 19.8": ["knocker"], "7.8 23.4 8.5": ["meddler"], "4.9 6.5 5.6": ["overpays"], "18.6 -2.9 17.4": ["charlotte"], "10.1 5.4 11.5": ["tabulator"], "-5.8 5.2 19.7": ["corkage"], "-0.2 -0.9 -5.7": ["tradename"], "6.5 18.7 1.3": ["lynchpins"], "-11.8 6.6 0.0": ["psychotherapeutic"], "4.9 12.6 20.4": ["honeypots"], "2.4 1.6 -0.1": ["underwritings"], "15.1 9.6 14.1": ["quadrilateral"], "12.5 9.3 20.9": ["mashers"], "-4.2 0.3 -4.2": ["homelike"], "-7.9 2.5 -0.0": ["librarianship"], "-4.0 -0.0 8.3": ["polyesters"], "-3.5 7.3 5.2": ["preconditioning"], "-9.8 7.3 -2.5": ["thromboembolism"], "-5.0 9.8 -2.3": ["narrowcast"], "6.6 2.8 5.7": ["ise"], "17.9 4.0 9.4": ["postindustrial"], "15.5 19.4 26.0": ["conker"], "-1.5 7.9 16.1": ["decolletage"], "11.5 17.3 10.5": ["baiter"], "5.3 4.0 16.7": ["floyd"], "1.2 9.1 8.9": ["cloudbursts"], "-8.5 6.6 11.8": ["reimposition"], "-1.2 26.3 4.3": ["reoccupying"], "2.8 11.7 15.5": ["comfortingly"], "-1.8 9.6 13.3": ["foliar"], "13.1 11.7 8.6": ["sloshes"], "-8.6 8.6 11.0": ["xeriscape"], "12.9 3.4 1.4": ["elec"], "2.8 2.0 11.4": ["stockier"], "0.9 21.3 4.9": ["spycraft"], "12.5 8.1 13.9": ["curdling"], "-8.1 10.2 14.7": ["authorizers"], "0.2 12.1 5.4": ["survivals"], "7.2 8.6 8.7": ["cosiness"], "5.3 18.0 6.5": ["conformism"], "8.4 1.8 8.0": ["filmstars"], "-2.6 13.9 10.7": ["intercedes"], "-4.8 15.3 21.5": ["orchardist"], "13.3 15.7 -1.6": ["equiped"], "6.7 11.6 4.4": ["fullerene"], "12.9 8.7 18.0": ["sextant"], "-1.3 14.5 9.7": ["toxicants"], "15.4 7.6 10.1": ["geekiest"], "7.2 2.4 -0.3": ["resurged"], "-7.6 3.3 10.1": ["greywater"], "-0.7 0.9 7.5": ["polyimide", "carrybacks"], "-2.4 18.5 1.6": ["purposefulness"], "-3.5 -0.5 3.5": ["powerlifters"], "11.3 20.1 -0.3": ["outsmarts"], "3.5 7.5 6.1": ["nitrosamines"], "6.0 4.0 54.7": ["hoki"], "6.2 7.2 5.2": ["flighting"], "8.3 13.1 9.6": ["beautifies"], "5.6 14.6 17.8": ["hookworm"], "3.3 5.6 22.7": ["borage"], "10.2 3.4 10.3": ["wis"], "-1.9 11.9 7.3": ["conformational"], "-2.1 13.1 4.3": ["bandgap"], "15.0 11.9 11.4": ["soapboxes"], "-4.2 9.8 5.8": ["infectiousness"], "0.5 9.4 7.0": ["leukopenia"], "9.2 6.6 6.9": ["constructional"], "3.9 13.4 7.1": ["acomplia"], "3.5 21.0 3.9": ["compunctions"], "4.2 26.0 14.2": ["tooltip"], "16.2 -3.6 8.6": ["cobblestoned"], "1.9 -6.6 1.5": ["tes"], "12.0 8.4 12.3": ["fesses"], "5.1 11.0 9.4": ["heterogenous"], "8.1 10.9 5.1": ["nontrivial"], "0.9 5.9 9.3": ["layins"], "-1.1 7.2 4.3": ["slenderest"], "12.7 12.9 15.7": ["freakshow"], "1.7 6.2 8.3": ["fettle"], "-0.7 20.3 6.0": ["salaam"], "5.6 -1.9 -1.1": ["polyol"], "6.0 19.5 12.9": ["lathi"], "18.2 3.8 5.4": ["inauspiciously"], "17.5 -1.0 0.2": ["mangement"], "12.9 10.3 15.1": ["hydrodynamics"], "4.4 16.4 0.6": ["otherhand"], "6.6 14.7 5.8": ["pranking"], "1.4 9.1 9.3": ["jimmied"], "14.9 7.5 4.6": ["teenyboppers"], "8.8 5.5 14.7": ["roy"], "-2.9 6.1 16.1": ["perry"], "7.2 6.4 4.6": ["roved"], "-1.8 9.4 6.2": ["disinherit"], "4.7 15.6 15.1": ["niggardly"], "4.0 11.5 -0.6": ["evangelise"], "1.7 2.1 2.5": ["pastiches"], "-1.4 4.6 2.2": ["ems"], "0.4 6.5 1.4": ["eeked"], "10.1 22.0 21.4": ["sonars"], "2.4 8.2 7.3": ["multiuser"], "-1.2 1.4 8.0": ["rsvp"], "14.6 8.0 14.3": ["coffeepot"], "-0.0 7.8 -1.2": ["viagogo"], "7.7 16.2 14.0": ["shadowboxing"], "5.2 2.1 33.8": ["tomatillo"], "8.5 20.4 7.2": ["multidirectional"], "7.7 14.1 8.7": ["keffiyeh"], "24.3 14.2 15.5": ["tetherball"], "1.2 4.3 4.2": ["scribing"], "8.7 6.0 14.3": ["gentrify"], "10.3 5.1 15.9": ["taillamps"], "5.9 1.9 -2.0": ["nonproprietary"], "12.7 9.0 19.4": ["edger"], "8.5 4.0 14.8": ["translucency"], "16.0 20.5 26.0": ["wormy"], "-8.2 2.1 10.0": ["oblasts"], "13.9 7.4 15.7": ["fuzzies"], "-3.2 17.4 5.5": ["designator"], "3.2 6.8 0.2": ["projectable"], "0.7 4.9 8.6": ["hemophiliac"], "12.4 19.0 15.0": ["dimness"], "2.8 12.8 18.2": ["broadleaf"], "-2.7 4.1 9.1": ["anencephaly"], "4.1 10.8 17.3": ["undercoat"], "0.4 2.9 -2.0": ["ile"], "8.6 -2.7 6.2": ["tramline"], "6.2 4.8 48.7": ["cockle"], "5.5 8.1 4.8": ["unionisation"], "-12.5 2.1 4.5": ["phenytoin"], "6.6 3.3 15.5": ["pickiest"], "3.2 11.4 6.0": ["counterbalances"], "1.8 3.7 35.5": ["farro"], "1.3 6.3 11.3": ["unmined"], "18.1 -5.5 13.3": ["trousered"], "8.1 13.4 8.6": ["unconfined"], "4.4 11.4 11.1": ["beatdowns"], "9.2 -1.1 11.6": ["biomed"], "0.3 5.7 11.8": ["ulcerations"], "11.8 1.8 14.9": ["jags"], "-0.2 10.1 5.9": ["mitotic"], "11.1 8.9 7.2": ["reawakens"], "0.1 2.0 -2.8": ["pentaerythritol"], "2.4 16.1 -5.0": ["sadhvi"], "3.8 13.6 15.4": ["youse"], "5.0 5.9 7.8": ["maharajas"], "0.5 4.2 7.9": ["abstemious"], "5.1 16.9 10.7": ["keepaway"], "13.0 4.9 19.2": ["loofah"], "-3.5 10.9 14.6": ["overspread"], "8.0 -1.7 14.3": ["unsorted"], "-14.7 -6.5 6.4": ["waitlisted"], "11.2 1.6 9.2": ["bijou"], "4.8 22.3 21.6": ["longbow"], "5.7 1.4 8.5": ["nz"], "-0.4 23.0 3.9": ["playcaller"], "5.1 10.8 7.8": ["humaneness"], "-6.8 -1.1 -2.1": ["disaffiliation"], "5.4 11.0 3.2": ["quandry"], "-2.6 11.8 4.4": ["idealization"], "10.6 4.0 8.9": ["slalomed"], "1.0 6.1 13.9": ["collarbones"], "11.8 17.7 6.7": ["physic"], "3.6 2.7 -0.4": ["wre"], "27.9 7.4 11.0": ["telcom"], "0.8 2.2 9.3": ["korfball"], "-4.3 3.5 10.2": ["inaugurals"], "7.8 17.9 7.3": ["physiognomy"], "-3.1 18.0 4.8": ["literarily"], "3.1 5.6 7.6": ["cus"], "-0.4 6.3 4.3": ["institutionalizes"], "1.6 10.7 6.2": ["saintliness"], "-0.1 12.7 9.7": ["presupposed"], "-1.0 5.5 3.6": ["marc"], "6.1 14.5 6.0": ["mystifyingly"], "9.3 8.7 0.7": ["maidan"], "5.5 12.2 29.1": ["pumpernickel"], "2.8 5.7 6.9": ["polypeptide"], "3.7 12.1 1.2": ["findable"], "12.3 14.5 7.1": ["razes"], "5.7 1.7 34.6": ["roulade"], "3.1 13.0 15.5": ["busywork"], "10.9 17.5 6.2": ["replicators"], "3.3 7.8 13.6": ["hutongs"], "13.6 2.3 12.4": ["flowlines"], "5.6 9.8 42.0": ["intertidal"], "2.6 1.6 16.8": ["carrageenan"], "13.6 0.9 11.6": ["shebang"], "-6.8 7.7 11.4": ["rubato"], "7.6 12.2 10.2": ["unreflective"], "2.9 7.1 12.8": ["gorgeousness"], "-5.2 20.7 3.6": ["subaltern"], "20.1 6.4 1.0": ["backoffice"], "13.3 2.0 12.2": ["madonna"], "1.8 7.5 5.5": ["sybaritic"], "15.2 18.9 12.5": ["flypaper"], "10.2 4.6 12.9": ["wearin"], "-2.8 3.8 -1.5": ["amici"], "-0.9 -1.7 13.6": ["reroofing"], "2.9 15.8 24.9": ["flintlock"], "19.5 5.8 18.7": ["profitless"], "7.0 6.9 -0.5": ["creds"], "9.0 13.3 8.1": ["undriveable"], "3.7 9.8 25.2": ["hydrophones"], "7.4 -1.1 15.8": ["bint"], "17.7 13.0 26.2": ["simians"], "4.8 11.4 10.5": ["fg"], "-5.3 19.1 2.5": ["fulminations"], "-8.6 5.8 13.3": ["heterozygous"], "2.1 9.2 9.5": ["pixelation"], "-8.8 4.3 9.4": ["criteriums"], "11.4 4.3 4.5": ["tiler"], "10.4 7.8 23.1": ["doorstops"], "27.5 6.5 14.7": ["giga"], "-1.8 27.4 4.8": ["victimizers"], "5.3 5.9 11.9": ["knicker"], "8.2 14.4 6.6": ["wimped"], "3.6 13.5 8.2": ["warbirds"], "-3.2 7.3 5.8": ["spiritedness"], "-5.1 16.9 6.7": ["sovereignist"], "5.3 2.4 16.4": ["flowline"], "2.5 16.3 9.4": ["outchanced"], "14.6 -2.2 12.9": ["summerlong"], "-0.3 -8.9 8.5": ["undersubscribed"], "-2.8 2.1 4.3": ["kilobits"], "-3.2 7.1 0.5": ["sind"], "-8.2 -1.8 -1.3": ["nocturia"], "7.2 10.1 21.3": ["bowsprit"], "12.7 16.4 11.5": ["weirdoes"], "1.0 7.0 8.9": ["stylization"], "-0.8 7.9 6.8": ["demat"], "7.1 16.0 5.3": ["unrepentantly"], "-4.9 6.5 6.5": ["scripter"], "-4.2 7.8 7.5": ["guestlist"], "-3.7 13.4 11.2": ["coronaviruses"], "6.6 7.1 13.1": ["desal"], "13.2 9.2 23.2": ["macarons"], "6.1 16.0 13.2": ["manchild"], "9.7 10.0 4.9": ["wilding"], "9.7 8.3 17.2": ["showier"], "12.2 10.2 52.5": ["longline"], "-1.7 8.2 10.9": ["eventer"], "15.2 4.4 5.7": ["unpatented", "ows"], "13.9 14.4 8.2": ["astroturfing"], "-4.1 5.0 8.3": ["polycrystalline"], "-3.4 5.2 -5.7": ["disaffiliate"], "15.7 7.5 0.9": ["acquistions"], "-0.6 13.9 9.8": ["bioleaching"], "-5.4 14.0 -0.6": ["combatted"], "9.2 2.6 -9.1": ["alos"], "14.9 10.7 24.1": ["macaroon"], "9.6 11.2 9.0": ["spellcheck"], "14.4 6.6 20.1": ["potbelly"], "13.2 18.8 19.2": ["meatheads"], "5.9 17.7 1.8": ["jeremiad"], "1.3 9.8 45.5": ["crabcakes"], "13.7 -4.7 0.6": ["adminstrators"], "-1.8 8.9 11.3": ["epoxies"], "-3.8 11.4 3.5": ["iatrogenic"], "8.4 17.1 12.6": ["kleptocratic"], "12.3 13.6 4.5": ["technophobes"], "11.1 7.9 4.5": ["burnishes"], "14.6 17.3 9.4": ["gyrocopter", "ashamedly"], "-8.7 21.9 4.3": ["theist"], "1.0 12.3 4.3": ["jailings"], "-3.6 7.0 6.6": ["centigrade"], "8.4 9.3 24.3": ["tuskers"], "29.6 3.1 -1.9": ["subsidary"], "14.9 6.9 10.1": ["securitizers"], "7.2 5.3 7.3": ["thx"], "-4.0 1.0 3.6": ["bosentan"], "-0.7 9.8 -1.4": ["propound"], "4.7 5.7 7.9": ["overlies"], "1.3 5.5 11.8": ["kno"], "15.3 11.7 9.5": ["heraldry"], "3.3 1.6 9.7": ["ui"], "6.8 9.1 15.4": ["inna"], "1.8 9.0 11.5": ["sortable"], "2.5 8.2 5.8": ["recompensed"], "-1.4 -1.4 2.3": ["hypomania"], "3.5 8.9 10.5": ["coulee"], "-3.9 0.0 -2.2": ["testings"], "10.7 6.3 4.3": ["brainier"], "9.1 10.5 7.7": ["binman"], "5.7 21.2 6.9": ["israeli"], "1.0 10.4 10.5": ["bitingly"], "-2.5 16.4 -1.6": ["dissuasive"], "0.3 -0.6 -0.4": ["soums"], "-4.9 9.2 1.5": ["immunising"], "-0.1 10.4 13.5": ["bigha"], "4.9 3.3 13.5": ["trois"], "3.2 7.5 19.5": ["logrolling"], "-0.5 8.5 2.6": ["endurable"], "-9.0 13.1 5.5": ["zoonotic"], "-0.9 2.5 0.9": ["eltrombopag"], "7.9 5.6 8.2": ["geeking"], "8.0 12.3 6.9": ["fabulist"], "8.6 21.9 2.4": ["gunfighters"], "13.8 1.6 10.8": ["maquettes"], "3.0 9.9 17.0": ["forebrain"], "9.2 13.8 21.7": ["striations"], "7.9 7.5 11.9": ["kleptomania"], "3.6 10.0 17.6": ["groms"], "-2.0 13.8 10.3": ["campiness"], "-2.0 12.8 11.4": ["karo"], "16.1 8.7 14.2": ["cushiony"], "9.8 7.3 16.5": ["spooktacular"], "4.9 11.0 9.6": ["heinousness"], "-1.4 5.7 3.4": ["xxii"], "-1.3 7.9 11.5": ["workfare"], "10.6 15.4 8.3": ["lucks"], "9.5 12.0 6.7": ["accreting"], "0.3 8.4 0.7": ["offhanded"], "7.3 17.1 12.5": ["kumbaya"], "7.6 11.9 13.9": ["lintel"], "16.6 4.3 0.3": ["bnn"], "-4.0 10.7 -2.6": ["expatriation"], "-4.4 9.1 9.0": ["repolling"], "1.8 7.1 12.5": ["eucharist"], "-0.1 1.2 6.4": ["transcoder"], "2.7 13.1 -0.6": ["adulatory"], "15.1 -1.4 24.4": ["deepsea"], "-2.6 17.0 21.6": ["griller"], "-3.4 15.6 3.6": ["rashness"], "2.4 4.1 -0.9": ["shortcode"], "7.4 -1.9 10.9": ["sportsplex"], "-12.1 7.2 7.7": ["freethrows"], "4.3 1.7 11.6": ["nito"], "2.6 13.2 16.3": ["growly"], "7.9 11.3 12.9": ["sysadmins"], "4.0 4.3 42.6": ["cioppino"], "8.3 3.5 1.7": ["mms"], "10.5 5.1 6.8": ["moseying"], "10.6 16.8 15.0": ["shalt"], "6.2 9.0 6.2": ["weepers"], "10.0 13.9 12.0": ["multination"], "6.8 1.2 13.6": ["bridegrooms"], "3.3 4.0 4.3": ["deadlocking"], "0.9 13.6 6.2": ["fmoore"], "-2.5 7.0 7.0": ["juve"], "4.7 25.4 19.7": ["defoliate"], "18.7 29.7 -0.4": ["outflanking"], "7.5 5.9 14.4": ["lowballed"], "-4.6 4.8 4.0": ["nonsignificant"], "-2.7 -1.9 5.5": ["chromate"], "11.4 8.4 7.4": ["hubbie"], "-2.3 11.4 5.2": ["throughway"], "3.0 5.1 7.1": ["shampooed"], "17.4 14.2 7.9": ["metamorphosing"], "-8.1 8.8 6.7": ["overrepresentation"], "2.7 -4.6 11.2": ["mae"], "5.7 16.8 12.1": ["habitants"], "6.2 9.7 9.9": ["gustiness"], "-4.0 4.4 11.0": ["mycotoxin"], "10.8 18.8 14.2": ["tomahawks"], "12.2 15.2 10.0": ["stickhandle"], "10.0 -3.2 12.7": ["melas"], "-3.2 3.2 0.3": ["bioethical"], "4.6 10.9 12.6": ["rugger"], "2.1 7.1 9.5": ["inseminate"], "-14.9 3.9 0.2": ["reinvestigating"], "16.2 3.8 5.9": ["crowdsource"], "-0.2 1.5 1.7": ["inserter"], "2.9 9.7 11.5": ["mera"], "0.5 -1.6 12.0": ["palmolein"], "0.5 21.7 23.9": ["treestand"], "14.3 3.7 5.9": ["marketeer"], "8.0 18.9 6.3": ["shrilly"], "-7.7 7.8 5.1": ["vinorelbine"], "-0.2 1.3 15.2": ["jai"], "-8.0 8.0 7.1": ["ceftriaxone"], "10.8 18.8 2.8": ["growingly"], "13.3 16.1 16.7": ["retch"], "-9.2 8.2 8.2": ["chloramines"], "15.9 5.4 12.3": ["coalminers"], "0.7 16.8 22.5": ["wobbler"], "0.1 2.5 7.2": ["noticably"], "11.0 9.9 23.8": ["souffles"], "-0.2 2.3 28.3": ["raita"], "4.2 2.9 3.5": ["genset"], "6.8 13.7 -0.0": ["chary"], "-1.2 13.0 9.2": ["hitouts"], "9.2 9.5 -2.0": ["leered"], "-4.4 1.0 8.1": ["charette"], "11.7 0.3 -0.0": ["uncouple"], "13.7 16.1 7.1": ["agressively"], "8.2 1.4 17.3": ["oregon"], "1.6 11.8 -1.6": ["atomization"], "5.6 16.6 6.1": ["obtuseness"], "1.1 -5.2 4.9": ["lancets"], "8.7 19.9 22.5": ["whitefly"], "-6.8 14.4 32.4": ["shoaling"], "1.7 11.7 9.1": ["erg"], "-4.8 -2.1 -2.0": ["neurobehavioral"], "8.9 2.1 10.6": ["agita"], "5.9 30.3 16.2": ["brigand"], "7.0 14.8 5.3": ["impetuosity"], "4.9 9.0 13.5": ["shadowbox"], "11.8 7.1 18.2": ["ventriloquists"], "-2.5 14.3 5.3": ["racialist"], "-1.3 13.4 2.5": ["caliphs"], "-1.2 22.3 3.1": ["ideologists"], "-0.3 2.9 8.9": ["boli"], "8.4 5.1 11.3": ["punchout"], "4.9 10.4 2.2": ["quaterback"], "7.7 7.0 40.9": ["cukes"], "3.8 25.8 9.6": ["counterrevolutionaries"], "14.5 16.9 26.8": ["palmettos"], "3.9 5.4 15.2": ["tinctures"], "4.9 17.1 2.5": ["votaries"], "2.6 2.4 7.1": ["bonusing"], "6.1 22.1 1.1": ["desperados"], "20.9 12.6 26.3": ["racoon"], "-7.0 8.4 -2.2": ["cadastral"], "5.0 2.2 7.7": ["readjusts"], "-2.1 0.7 3.5": ["nal"], "3.4 7.9 14.5": ["jamband"], "6.8 8.2 8.0": ["nonmetallic"], "2.2 12.5 20.6": ["bottomlands"], "4.5 18.1 19.6": ["forkball"], "9.7 0.5 1.3": ["ellipticals"], "10.6 2.4 8.6": ["sponged"], "7.4 3.9 7.7": ["brimful"], "-2.5 5.6 6.1": ["preowned"], "7.0 10.5 5.8": ["mollycoddled"], "14.4 10.6 13.0": ["tweezer"], "11.1 7.5 11.4": ["harrumphing"], "6.0 14.9 12.6": ["predication"], "0.8 3.1 15.4": ["shophouse"], "0.3 6.9 22.0": ["gaya"], "10.2 11.5 6.6": ["kinematic"], "19.0 21.7 4.9": ["megalomaniacs"], "10.0 13.7 6.0": ["appall"], "-1.9 4.7 2.1": ["oco"], "13.1 23.6 7.5": ["desecrates"], "5.5 12.2 2.5": ["reboard"], "-4.9 4.7 0.8": ["intravascular"], "7.5 19.3 4.2": ["utopians"], "-3.8 4.8 -1.3": ["neuropathic"], "2.4 12.1 15.7": ["noroviruses"], "12.9 17.6 12.2": ["brotha"], "-7.9 5.5 2.2": ["committ"], "17.2 15.7 18.0": ["codpiece"], "24.5 18.1 7.2": ["swooshing"], "15.5 15.5 5.7": ["vortexes"], "12.0 10.1 6.0": ["wrongfooted"], "6.5 -7.1 8.0": ["gabbed"], "7.8 7.7 -0.5": ["underworked"], "1.3 2.3 19.4": ["fluvial"], "-2.7 -10.5 5.5": ["particpate"], "0.4 13.4 1.0": ["unaccepted"], "17.4 21.2 18.6": ["disembowel"], "1.2 0.1 11.8": ["kilohertz"], "7.1 4.4 5.2": ["workhouses"], "4.3 15.4 9.5": ["kiddin"], "4.0 15.9 19.9": ["cusses"], "-0.2 12.6 0.3": ["writable"], "3.8 5.3 8.9": ["skycap"], "-2.2 8.7 4.3": ["semfinals"], "12.6 11.0 3.9": ["locater"], "0.2 8.7 3.0": ["angioedema"], "5.5 6.4 6.9": ["pneumoconiosis"], "0.5 6.4 2.9": ["longwinded"], "-0.4 4.0 16.7": ["snowier"], "8.6 3.2 27.4": ["tartlets"], "-0.1 3.3 7.7": ["weathercaster"], "5.7 0.3 6.2": ["neurotechnology"], "17.1 11.3 44.9": ["crawdad"], "21.5 10.8 7.5": ["juddering"], "-5.0 2.0 -4.3": ["nikahnama"], "8.4 3.1 -2.4": ["backings"], "-1.7 8.4 10.9": ["whodunits"], "5.1 5.3 8.3": ["tensioned"], "1.4 -4.8 8.5": ["mtpy"], "-5.0 -2.3 11.2": ["mel"], "-10.5 7.9 0.8": ["oncologic"], "5.3 12.8 6.3": ["cyberbullies"], "4.8 -0.5 -0.4": ["playbills"], "-1.2 5.0 8.5": ["flowsheet"], "-0.6 -3.0 23.1": ["lagniappe"], "-4.7 0.9 7.1": ["sey"], "-6.5 8.8 -0.7": ["estopped"], "5.4 4.3 9.0": ["stateline", "yamaha"], "-0.3 13.9 5.7": ["unneccessary"], "10.5 5.3 17.3": ["sunbather"], "0.7 2.2 2.7": ["newsboys"], "-0.8 2.3 11.9": ["jumpstarts"], "-16.6 10.5 6.8": ["incompletes"], "18.2 0.1 13.1": ["unlabelled"], "14.0 11.5 10.3": ["preens"], "-10.9 3.0 6.5": ["fluoroquinolone"], "12.7 15.4 16.3": ["goofily"], "2.6 15.0 15.2": ["playacting"], "2.3 5.1 0.2": ["disinvested"], "11.9 14.3 19.0": ["regrowing"], "-1.9 8.9 3.6": ["eighthman"], "14.5 -3.4 -2.3": ["creditwatch"], "13.8 20.9 16.8": ["phasers"], "-14.7 9.4 -0.5": ["corroborative"], "9.6 6.6 22.4": ["roadrunners"], "7.8 -2.5 7.2": ["fivers"], "11.5 10.1 43.8": ["gizzard"], "-6.4 5.0 -3.3": ["reversionary"], "-9.3 9.0 1.3": ["selectees"], "-2.6 6.4 22.9": ["bodysurfing"], "8.5 9.1 18.3": ["hurley"], "0.2 -2.5 11.5": ["nongaming"], "2.5 9.5 36.3": ["udon"], "-6.2 8.8 2.5": ["cardiotoxicity"], "-5.0 8.4 7.1": ["stover"], "2.4 12.0 4.0": ["absorptive"], "9.2 10.0 19.5": ["northwoods"], "-5.6 2.1 2.5": ["elagolix"], "7.6 6.4 24.9": ["restuarant"], "-1.6 15.7 7.4": ["adaptively"], "1.0 9.6 8.5": ["voxel"], "0.2 -1.7 2.8": ["unplayed"], "-2.4 5.2 8.1": ["subparagraph"], "5.5 9.6 7.7": ["nutmegged"], "4.9 12.8 7.1": ["grafters"], "0.6 -2.6 8.0": ["itaas"], "12.4 12.1 24.1": ["thylacine"], "20.2 -0.9 9.1": ["billlion"], "3.3 9.3 23.2": ["mack"], "8.5 8.2 29.1": ["popovers"], "6.2 14.9 9.5": ["nosecone"], "1.6 6.7 6.7": ["hve"], "-9.0 -0.2 11.4": ["fruitier"], "1.3 10.5 11.5": ["ihug"], "6.6 11.2 14.5": ["webserver"], "8.3 10.7 7.2": ["chirality"], "7.8 15.9 13.2": ["ultraconservatives"], "2.2 15.4 8.5": ["stoker"], "7.0 5.1 14.2": ["glazier"], "1.6 4.9 30.7": ["hoisin"], "4.1 -10.2 -0.7": ["factsheets"], "5.5 6.9 25.3": ["megayachts"], "4.1 9.2 4.1": ["minutest"], "9.0 4.9 8.9": ["youd"], "0.2 1.9 10.0": ["breakway"], "-1.4 7.7 0.0": ["tortious"], "10.4 14.2 15.0": ["christ"], "-1.5 6.9 4.0": ["defragmenting"], "12.8 13.1 13.9": ["foreshortened"], "4.9 11.7 6.0": ["garble"], "-4.4 14.9 0.9": ["empathetically"], "0.3 12.0 13.4": ["sobers"], "-0.5 2.8 5.1": ["uplevel"], "-4.2 1.1 -1.5": ["longlisted"], "-2.1 4.5 9.4": ["screencast"], "13.8 26.1 20.6": ["broadsword"], "16.2 7.9 13.8": ["paling"], "8.8 7.9 14.2": ["mandalas"], "-0.7 5.1 -0.8": ["backslaps"], "4.9 5.7 9.4": ["citified"], "8.5 2.3 29.2": ["filo"], "-1.5 8.7 4.7": ["ints"], "2.3 4.9 30.2": ["seitan"], "6.7 3.2 23.6": ["gladioli"], "12.3 11.9 0.5": ["boomboxes"], "2.3 10.3 5.9": ["microgrid"], "-6.7 2.2 5.9": ["insurability"], "6.1 -1.7 8.8": ["biobank"], "14.3 5.4 5.6": ["pivotals"], "4.3 11.7 28.8": ["crabapples"], "-11.9 17.8 2.0": ["untruthfulness"], "-0.3 0.8 30.4": ["pollo"], "7.8 17.7 8.8": ["congresspeople"], "4.1 5.4 3.8": ["benifits"], "-0.7 10.8 8.4": ["cueist"], "4.0 -2.6 9.9": ["ded"], "3.8 6.6 4.9": ["derecognised"], "0.5 2.0 8.3": ["roundtripper"], "16.9 14.2 12.1": ["drumroll"], "11.2 23.4 17.7": ["ragdoll"], "10.1 11.9 6.0": ["nontransparent"], "26.8 6.2 18.4": ["pincushion"], "-2.1 4.6 -2.1": ["redevelops"], "-2.9 8.2 3.7": ["disclosable"], "7.3 6.4 11.5": ["alo"], "-2.2 4.8 19.9": ["pisco"], "6.1 12.0 5.7": ["endo"], "-1.0 12.3 -2.6": ["misdiagnose"], "3.2 8.6 6.9": ["subscribership"], "-2.4 -0.0 -1.7": ["ovs"], "10.8 -2.1 14.2": ["dai"], "-11.6 3.9 -0.9": ["reoperation"], "-6.6 6.0 0.5": ["pregabalin"], "4.5 0.2 27.2": ["verde"], "14.2 9.2 9.6": ["agora"], "13.6 30.1 3.6": ["cavalrymen"], "6.3 21.6 1.7": ["proconsul"], "5.8 3.0 6.9": ["swanning"], "10.2 7.4 -3.1": ["leeched"], "6.1 9.6 13.6": ["sixer"], "-4.7 1.6 -4.8": ["treatement"], "-7.1 13.1 1.7": ["legitimated"], "8.3 2.8 4.5": ["lik"], "4.2 8.9 12.5": ["oversleep"], "11.2 -5.5 -2.7": ["bv"], "13.7 5.9 5.9": ["bastardised"], "-6.7 3.0 10.2": ["supervisorial"], "-1.9 12.9 13.3": ["daypack"], "-4.1 18.6 6.7": ["pugnacity"], "3.9 3.4 6.2": ["ests"], "12.0 5.7 6.2": ["foor"], "11.1 3.7 6.1": ["callipers"], "0.7 18.2 6.1": ["nonintervention"], "1.7 5.9 4.6": ["rulebooks"], "4.4 2.7 6.0": ["pri"], "3.5 5.7 13.2": ["glaciologists"], "-0.4 7.4 17.9": ["snicked"], "8.1 15.3 8.5": ["screwups"], "-12.1 17.1 4.1": ["counterdrug"], "-6.0 17.7 9.0": ["transgresses"], "9.8 -2.8 2.5": ["precociously"], "1.7 0.1 3.5": ["pharmacogenetic"], "11.9 3.3 12.6": ["townscape"], "5.1 15.6 17.6": ["redskins"], "0.2 6.4 4.4": ["sixtieth"], "2.7 22.0 5.2": ["cultic"], "6.4 7.2 2.2": ["labled"], "4.2 9.1 14.1": ["grossness"], "-1.1 20.3 26.3": ["tablemates"], "11.5 0.5 12.8": ["zaftig"], "12.6 7.5 7.1": ["hemispherical"], "1.5 -3.4 11.9": ["embryologist"], "-2.0 14.8 -0.1": ["teamates"], "0.1 20.2 6.4": ["foreignness"], "4.1 5.5 17.8": ["crusting"], "-0.7 1.9 1.3": ["tetralogy"], "7.1 7.3 35.1": ["sambal"], "-2.5 6.5 2.1": ["lacosamide"], "15.4 5.2 5.1": ["biomimicry"], "-7.4 -7.3 3.6": ["ethnomusicologist"], "-8.1 -2.9 3.5": ["invivodata"], "9.3 16.9 9.7": ["effectors"], "-1.5 7.3 -0.9": ["incepted"], "7.3 8.3 30.7": ["frittatas"], "5.9 11.7 10.1": ["bunkhouses"], "5.3 14.3 3.0": ["newsweeklies"], "5.5 1.2 23.2": ["prasadam"], "36.5 4.9 25.2": ["brontosaurus"], "4.7 7.5 20.4": ["sweetmeats"], "-0.6 22.7 3.3": ["rulership"], "8.0 23.3 11.1": ["joypad"], "9.7 9.8 7.5": ["outa"], "12.4 2.0 17.8": ["innertube"], "13.9 26.4 1.4": ["avengers"], "6.1 8.6 -1.4": ["freenet"], "9.5 0.4 2.1": ["swopped"], "-2.0 10.0 9.3": ["incurably"], "0.7 17.1 3.7": ["unkown"], "-5.5 5.8 8.0": ["saxes"], "14.2 0.3 31.6": ["cauliflowers"], "11.1 5.8 5.0": ["twanging"], "8.3 7.5 16.9": ["nonorganic"], "2.2 16.5 13.2": ["covetousness"], "-2.5 7.3 7.6": ["colorway"], "-6.8 13.1 12.8": ["candida"], "-0.8 9.1 7.2": ["departement"], "-0.5 -6.6 6.3": ["weightloss"], "7.3 10.1 15.8": ["sirs"], "6.2 1.6 0.5": ["airmailed"], "1.7 -0.7 9.6": ["dura"], "11.0 13.3 8.6": ["nonconsensual"], "-1.3 10.3 8.5": ["generationally"], "20.5 4.3 2.0": ["bestrode"], "23.2 10.9 18.0": ["dirigibles"], "17.6 7.2 7.1": ["ultracompetitive"], "2.7 15.7 9.8": ["zithromax"], "10.2 -3.8 6.2": ["squiring"], "9.0 7.0 6.8": ["pelvises"], "9.7 23.4 6.0": ["mythmaking"], "-0.0 8.4 0.6": ["intrest"], "-4.6 7.5 13.0": ["mouthguards"], "2.9 11.3 15.2": ["cairns"], "7.5 20.1 9.8": ["adjacency"], "2.1 9.1 11.4": ["softballers"], "0.6 12.7 16.0": ["workpieces"], "-10.0 3.5 5.9": ["understudying"], "4.0 16.4 9.1": ["narc"], "8.7 1.2 14.1": ["hijinx"], "14.6 -0.8 12.3": ["marimbas"], "13.3 5.2 6.2": ["pyres"], "-7.8 4.2 1.1": ["genitourinary"], "-2.2 8.8 4.4": ["pigeonholes"], "-0.8 -1.3 3.4": ["iam"], "7.7 1.6 9.0": ["snowsuits"], "-0.8 -1.4 5.7": ["tolas"], "15.5 0.7 -1.3": ["doyens"], "-9.8 4.8 -2.3": ["civically"], "-6.5 9.4 12.3": ["swimmable"], "6.6 9.0 7.2": ["slags"], "3.0 7.6 4.5": ["foresighted"], "-1.6 17.2 9.7": ["laches"], "6.6 5.3 3.8": ["blag"], "-1.1 6.9 6.1": ["lignans"], "9.2 -2.3 13.0": ["humidors"], "11.9 11.4 14.0": ["linesperson"], "-4.0 8.1 2.7": ["detoxified"], "1.5 4.6 3.0": ["mywaves"], "8.0 12.5 7.7": ["antiphishing"], "11.4 2.0 9.5": ["ope"], "1.2 10.3 12.4": ["kathak"], "3.8 7.6 20.8": ["gondoliers"], "-4.5 14.4 12.0": ["analyte"], "10.9 19.6 6.1": ["kleptocrats"], "1.3 10.0 10.2": ["assignations"], "4.7 5.6 1.5": ["marabouts"], "7.1 11.7 8.7": ["rafa"], "-0.7 15.1 8.0": ["misfortunate"], "-0.9 -1.2 10.9": ["sevenths"], "9.5 11.6 6.6": ["deindustrialization"], "-0.4 9.4 5.3": ["pleural"], "6.1 0.7 5.8": ["wasa"], "8.3 9.3 13.8": ["nyet"], "5.8 13.3 17.0": ["leapers"], "3.9 10.7 7.2": ["considerately"], "5.8 14.9 14.2": ["sundowners"], "6.7 1.1 5.0": ["whch"], "15.5 6.9 11.3": ["carnivalesque"], "5.4 14.7 47.1": ["bloodworms"], "10.4 12.8 13.0": ["mornin"], "0.8 12.0 11.0": ["auxin"], "12.3 11.1 8.2": ["cowpokes"], "7.1 13.1 7.7": ["xls"], "-3.9 -0.6 9.6": ["levamisole"], "-8.5 -0.3 7.8": ["pledgers"], "7.8 5.1 12.8": ["autotune"], "9.3 8.0 13.7": ["luciferase"], "5.5 7.2 17.7": ["snifter"], "2.1 14.5 11.5": ["homeostatic"], "-0.1 8.5 7.2": ["classist"], "-3.6 10.2 7.8": ["retinoids"], "2.9 8.8 2.0": ["wireframes"], "9.4 12.9 6.3": ["madwoman"], "-7.9 15.0 0.7": ["misquotes"], "0.4 13.6 12.4": ["grayness"], "-5.1 7.4 11.4": ["langar"], "4.3 15.0 13.3": ["cutup"], "14.8 21.8 6.0": ["dragooned"], "-0.3 5.6 5.7": ["abled"], "-5.9 11.3 2.1": ["unfitting"], "19.9 5.7 15.7": ["minicomputer"], "5.7 3.7 5.1": ["linage"], "12.8 9.7 20.2": ["neds"], "6.1 1.2 12.0": ["bullriding"], "1.7 7.0 15.1": ["biomonitoring"], "8.7 9.5 9.6": ["filch"], "-0.5 12.5 31.0": ["vinaigrettes"], "-1.9 -1.2 -8.8": ["thesame"], "11.7 2.1 12.8": ["hoss"], "3.2 8.0 -1.1": ["condescended"], "-8.5 1.6 3.0": ["cantorial"], "-4.7 -5.9 7.8": ["belatacept"], "2.8 20.9 25.8": ["drakes"], "9.7 7.1 8.3": ["stormiest"], "1.8 7.9 6.0": ["sorer"], "-4.8 16.4 -0.6": ["upholders"], "7.6 11.7 13.0": ["grandkid"], "14.2 -0.4 -6.2": ["headquarted"], "0.3 19.4 11.1": ["caver"], "-0.2 -3.6 3.4": ["casebook"], "-0.4 11.9 15.3": ["putaway"], "1.7 1.2 11.7": ["glycolysis"], "1.5 7.2 21.7": ["cays"], "0.0 4.8 16.8": ["roma", "bandang"], "0.9 3.8 32.7": ["peelers"], "9.3 11.8 6.9": ["fractiousness"], "12.5 16.3 -1.2": ["subsuming"], "0.3 12.1 2.6": ["toughly"], "16.4 8.4 28.6": ["chippie"], "2.2 10.6 5.1": ["aand"], "-2.6 -5.7 8.3": ["rhapsodize"], "11.5 -0.4 9.9": ["scrabbled"], "9.9 -3.2 8.8": ["flusher"], "-1.5 4.2 0.8": ["prosthetist"], "10.0 10.0 13.6": ["sharer"], "4.3 9.5 25.5": ["brassicas"], "-7.7 6.7 16.3": ["uninsurance"], "3.9 -0.3 5.0": ["cette"], "5.7 3.9 7.3": ["boccia"], "6.4 0.8 9.3": ["ross"], "5.8 17.0 -1.1": ["threating"], "2.0 -1.4 15.6": ["siyang"], "9.2 7.0 2.6": ["padlocking"], "10.0 10.5 7.9": ["chewers"], "13.8 -2.4 1.8": ["tarting"], "3.5 4.0 -1.6": ["conjugates"], "-4.8 4.5 4.9": ["competiting"], "10.2 9.5 15.4": ["micelles"], "5.4 34.5 7.2": ["transgressor"], "-0.4 -2.7 6.3": ["conc"], "3.5 11.1 14.8": ["twas"], "6.9 0.4 -2.3": ["restyle"], "5.9 4.5 5.7": ["slumdwellers"], "-1.5 2.0 0.9": ["decl"], "0.1 6.1 13.3": ["trailered"], "6.9 15.3 13.8": ["jist"], "0.4 0.0 6.4": ["rusticated"], "-5.1 12.5 2.6": ["declamatory"], "2.0 7.9 -1.9": ["corporative"], "16.7 8.9 7.8": ["snoozes"], "0.6 11.2 -0.8": ["undergirded"], "-8.3 5.9 2.3": ["prescheduled"], "6.9 1.8 2.1": ["underpenetrated"], "14.5 32.4 15.3": ["hexes"], "-0.1 1.6 12.5": ["boardshorts"], "3.5 0.7 8.1": ["abo"], "-1.3 11.2 9.9": ["impeachments"], "6.1 1.1 10.5": ["eun"], "5.1 7.7 9.1": ["homology"], "14.6 13.2 13.1": ["meretricious"], "-3.1 13.8 4.1": ["arguements"], "4.2 11.9 4.6": ["equivocations"], "9.1 9.9 1.9": ["genderless"], "8.9 3.0 15.3": ["feng"], "7.3 21.2 4.3": ["prostration"], "10.9 13.6 16.5": ["caissons"], "1.6 2.9 18.4": ["tobaccos"], "8.9 30.4 7.1": ["villians"], "8.4 18.3 14.5": ["hellishly"], "9.9 5.3 25.8": ["rashers"], "4.0 6.0 18.7": ["savouries"], "-0.6 1.1 11.5": ["sportscasting"], "-4.5 14.2 3.8": ["reproducibly"], "-0.8 1.6 11.0": ["grumpier"], "2.2 17.9 18.5": ["afterguard"], "11.7 13.3 17.1": ["birdflu"], "1.4 15.5 8.7": ["autoresponder"], "0.7 -6.9 4.9": ["acrylonitrile"], "2.8 17.7 4.6": ["frontiersmen"], "10.2 19.1 5.9": ["spitefully"], "-4.7 18.1 13.9": ["codependent"], "6.2 4.8 5.6": ["localizes"], "1.3 10.6 2.1": ["disaggregation"], "6.0 17.0 5.6": ["extradites"], "6.5 -0.0 8.3": ["nto"], "0.7 -0.8 6.2": ["decribed"], "7.4 6.3 29.7": ["tapa"], "9.8 0.2 4.1": ["aaa"], "-2.7 -3.2 8.7": ["prenups"], "9.0 5.2 8.1": ["reclogging"], "9.8 6.5 7.7": ["qwerty"], "6.0 13.0 12.7": ["palin"], "7.1 7.7 -1.9": ["dumfounded"], "7.1 -0.2 13.8": ["chong"], "3.0 1.2 13.4": ["dca"], "1.1 5.7 13.7": ["castmember"], "12.3 17.4 12.4": ["gyroball"], "12.9 6.6 19.9": ["sawhorses"], "6.4 7.0 8.1": ["unhealthily"], "2.7 21.7 1.0": ["tornadic"], "-2.6 8.6 2.0": ["maketh"], "6.3 0.6 -1.2": ["reaccelerate"], "16.9 1.8 33.1": ["gloppy"], "15.8 11.3 0.3": ["fluidic"], "11.9 9.1 13.0": ["nightlong"], "18.8 11.2 15.1": ["multicellular"], "3.5 6.9 19.9": ["toking"], "-8.4 5.8 16.3": ["merlots"], "14.1 18.0 13.9": ["manikin"], "5.5 -1.5 -0.1": ["unter"], "20.7 -2.3 2.9": ["lastminute"], "-9.6 3.1 10.8": ["oratorios"], "9.3 7.1 13.7": ["jointing"], "5.2 6.2 14.1": ["semisubmersible"], "9.1 14.5 3.4": ["luridly"], "-5.4 16.3 7.2": ["woundings"], "5.9 2.8 9.1": ["eukaryotic"], "-1.0 8.8 16.4": ["areola"], "-2.8 6.5 9.4": ["riddim"], "4.8 6.9 6.2": ["synthpop"], "18.4 12.7 21.5": ["pegboard"], "7.9 7.3 9.8": ["brainteasers"], "-1.5 15.8 6.9": ["workaholism"], "1.2 2.2 3.6": ["rezones"], "-0.4 1.6 2.7": ["frist"], "5.0 10.7 52.0": ["toothfish"], "2.4 11.2 33.4": ["gizzards"], "16.2 9.1 15.1": ["thunderheads"], "9.5 8.4 -1.1": ["coronated"], "9.1 19.6 14.7": ["caudillo"], "1.0 7.7 4.8": ["theorise"], "-7.2 9.7 -1.8": ["strangulations"], "11.8 21.3 29.8": ["arthropod"], "19.8 16.1 8.8": ["cubical"], "-3.5 13.7 8.1": ["placekickers"], "-4.7 7.8 9.5": ["aromatase"], "5.5 6.1 8.8": ["macintosh"], "0.6 16.7 7.1": ["chameleonic"], "1.4 1.8 30.4": ["nabe"], "4.4 19.6 12.0": ["untrusting"], "20.4 4.8 8.5": ["millionairess"], "11.0 26.7 9.4": ["terminators"], "11.8 11.0 15.5": ["petroglyph"], "1.6 4.1 6.8": ["petascale"], "8.3 12.7 3.3": ["obfuscations"], "-2.2 5.2 9.9": ["clefts"], "4.2 9.3 6.9": ["sussing"], "-9.2 2.0 6.5": ["capias"], "3.5 4.8 13.7": ["tyrosine"], "-0.1 13.2 -0.3": ["shouldn"], "1.2 3.2 3.6": ["continuos"], "6.1 -5.7 2.5": ["mont"], "-6.8 11.0 -0.6": ["broadminded"], "0.7 1.1 6.8": ["pipelined"], "13.7 15.1 12.5": ["dextrous"], "3.1 16.0 -1.4": ["responsability"], "-1.5 -1.3 -3.3": ["vita"], "5.2 -0.2 9.8": ["wayne"], "12.9 7.0 26.6": ["fromage"], "17.9 -1.3 11.6": ["flouncing"], "9.4 4.6 7.8": ["multipage"], "13.1 16.1 19.4": ["litterers"], "4.0 14.3 11.2": ["carbonaceous"], "-4.1 21.0 6.2": ["steganography"], "6.3 5.7 8.9": ["concatenation"], "6.4 9.9 1.3": ["multicounty"], "4.8 11.1 10.8": ["skiercross"], "11.5 1.3 -5.8": ["unplugs"], "-0.3 0.4 -0.4": ["accessibly"], "-5.9 -4.6 11.1": ["kurtis"], "-1.9 -8.1 10.9": ["updos"], "0.9 -8.8 -2.6": ["tional"], "1.2 5.1 4.1": ["torquey"], "2.9 9.8 5.7": ["intercooled", "econometrician"], "1.5 -2.7 15.7": ["jennifer"], "-7.8 10.6 5.2": ["catechist"], "7.6 8.8 14.0": ["showtunes"], "12.1 13.9 13.8": ["hedgies"], "-0.7 3.9 15.9": ["hardtail"], "8.6 11.3 7.9": ["goverments"], "8.9 10.8 3.1": ["themsleves"], "9.8 5.9 11.8": ["exhorbitant"], "11.9 2.4 6.8": ["styrenics"], "6.7 7.3 4.6": ["bedcovers"], "-0.2 8.7 5.3": ["intergroup"], "8.6 12.0 7.6": ["salivation"], "11.3 7.9 5.0": ["unphased"], "-5.6 18.2 10.4": ["medivac"], "-4.1 20.7 9.3": ["mistrusting"], "14.6 1.2 9.8": ["minimart"], "9.1 -3.5 3.5": ["gusset"], "1.7 1.7 -0.2": ["vich"], "1.2 1.1 12.6": ["gaited"], "1.9 4.2 7.0": ["hoosegow"], "1.3 14.8 -1.8": ["romanticise"], "-0.5 7.1 11.9": ["homeplace"], "1.3 7.1 15.0": ["limonite"], "2.6 2.7 10.0": ["calenders"], "-8.0 14.3 3.6": ["unhealed"], "8.4 10.1 -0.0": ["hardwire"], "9.0 10.3 18.7": ["adders"], "18.4 5.7 19.9": ["striated"], "-1.9 13.1 5.9": ["preselections"], "16.7 19.1 12.2": ["proles"], "13.9 5.8 0.1": ["diddy"], "5.3 17.4 9.6": ["fermenter"], "-6.1 9.3 8.8": ["sapacitabine"], "5.9 6.3 14.4": ["cheeriness"], "6.7 10.2 13.0": ["ragga"], "-8.5 -2.3 10.2": ["dore"], "6.2 8.8 11.3": ["eventuates"], "5.4 4.3 16.6": ["rotaries"], "2.6 15.7 6.3": ["paleness"], "11.5 9.5 19.7": ["addictively"], "6.4 17.2 2.9": ["sleazeball"], "9.2 -3.9 14.0": ["fedex"], "-10.8 2.9 -1.4": ["attenders"], "-1.5 7.2 -1.8": ["shd"], "6.3 -4.6 1.5": ["prettied"], "9.3 20.6 10.3": ["aversions"], "0.4 0.6 8.2": ["gamedays"], "-3.7 1.5 -3.1": ["mortgagors"], "-4.8 -0.3 8.3": ["microenterprises"], "1.9 3.2 10.3": ["precociousness"], "6.9 14.7 10.8": ["keytar"], "-3.3 5.0 22.6": ["diking"], "-3.1 9.1 11.6": ["rhabdomyosarcoma"], "9.0 16.3 7.4": ["biohazards"], "4.7 10.0 20.6": ["puddling"], "19.1 -0.3 10.2": ["bewigged"], "-0.5 10.9 -1.2": ["philology"], "-2.0 13.6 2.0": ["opinon"], "9.3 2.6 10.1": ["superfruit"], "16.8 4.3 17.3": ["extruding"], "4.7 -3.4 10.1": ["wastepaper"], "4.2 4.6 26.8": ["caraway"], "-0.8 9.0 3.2": ["eclampsia"], "-3.0 3.7 -2.2": ["isobutanol"], "4.6 14.2 8.3": ["witching"], "3.8 9.7 8.9": ["biolab"], "-11.6 7.3 -1.1": ["draftable"], "-3.0 4.1 12.7": ["serological"], "7.4 8.4 1.4": ["reposing"], "11.4 24.2 19.3": ["coldblooded"], "6.2 8.4 7.5": ["clotheshorse"], "9.2 30.8 9.5": ["bayoneted"], "-4.7 0.2 -0.5": ["echocardiographic"], "-4.7 -4.8 10.0": ["mesotherapy"], "8.8 7.0 8.9": ["tamest"], "13.9 5.9 29.4": ["coelacanth"], "2.9 5.5 13.3": ["syntactic"], "-8.3 1.6 10.3": ["nonschool"], "6.3 12.3 1.4": ["sanctimoniously"], "8.5 18.1 13.4": ["sublimity"], "6.4 3.0 4.1": ["satirised"], "-1.3 1.5 4.6": ["molders"], "12.0 5.7 1.0": ["frogmarched"], "7.2 15.1 -5.8": ["evangelising"], "4.3 2.4 10.9": ["kwa"], "-1.1 9.2 7.4": ["prostatitis"], "2.9 5.6 16.4": ["fens"], "-1.3 10.6 3.7": ["passcodes"], "-5.2 12.1 8.8": ["chlorinating"], "-6.9 7.7 9.6": ["malaysiakini"], "3.1 -2.3 12.9": ["xenotransplantation"], "11.0 6.0 -0.7": ["bioengineers"], "11.0 13.6 26.7": ["cottony"], "3.0 13.1 7.8": ["piercingly"], "7.2 14.2 13.6": ["handholds"], "3.2 9.0 8.5": ["telescoped"], "11.0 10.6 9.6": ["amphitheatres"], "14.6 -0.7 -0.7": ["ebit"], "11.2 33.5 6.0": ["hyperpower"], "3.6 11.7 16.3": ["gil"], "1.4 6.9 4.5": ["ghd"], "1.0 -1.9 13.5": ["boutonnieres"], "-5.9 15.1 8.4": ["legitimation"], "15.9 12.9 17.7": ["ravenously"], "16.2 20.5 10.7": ["pigheaded"], "20.1 15.7 10.7": ["plutocrat"], "-2.8 3.4 6.3": ["walkon"], "9.8 14.5 13.0": ["photorealism"], "-3.5 3.0 1.6": ["unexpurgated"], "0.3 6.1 4.8": ["prefeasibility"], "1.1 8.6 6.7": ["murderabilia"], "-12.4 -3.4 7.7": ["prefiled"], "14.7 28.2 5.0": ["telekinetic"], "-11.7 5.3 4.9": ["hypercalcemia"], "0.9 13.7 3.4": ["overrating"], "5.4 2.1 26.6": ["elderberries"], "7.7 13.5 11.6": ["tryless"], "1.4 4.0 12.5": ["minima"], "-0.5 2.2 6.2": ["duetted"], "11.9 10.1 17.3": ["congresspersons"], "15.2 2.2 27.6": ["glace"], "-2.9 15.4 8.0": ["limbic"], "4.7 13.3 10.9": ["kerchiefs"], "-6.7 9.8 10.0": ["oenophile"], "-5.1 8.4 0.5": ["renumbered"], "-4.9 3.1 3.2": ["underlayment"], "12.3 7.2 7.9": ["finanical"], "-0.4 6.2 -0.1": ["appends"], "2.4 6.7 28.7": ["cannolis"], "-10.4 13.4 -1.0": ["categorizations"], "0.3 8.4 25.8": ["keelboats"], "-0.1 15.1 11.8": ["sleeting"], "3.3 6.9 22.6": ["maria"], "11.2 9.0 5.9": ["pleasuring"], "8.3 4.1 32.2": ["coulis"], "13.2 11.0 14.7": ["backplate"], "2.9 1.0 10.4": ["maisonettes"], "11.1 6.7 23.5": ["philly"], "-1.5 20.2 8.8": ["presupposition"], "-0.5 3.1 39.8": ["canvasback"], "3.4 7.9 24.6": ["izakaya"], "4.0 2.7 7.2": ["cpl"], "4.8 13.9 3.4": ["decipherable"], "0.1 -0.4 3.8": ["marksheets"], "2.7 1.9 22.6": ["bodyboard"], "10.7 7.6 31.5": ["gouda"], "5.0 3.4 2.0": ["extroversion"], "-1.4 5.6 7.7": ["litterateurs"], "4.2 2.1 0.2": ["misclassifying"], "5.7 0.2 -0.7": ["trainloads"], "16.4 9.2 15.1": ["waterwheel"], "-0.5 -4.6 12.0": ["anne"], "15.5 16.6 20.3": ["faeries"], "4.7 13.5 2.7": ["sanitisation"], "5.2 7.9 11.7": ["preadolescent"], "-0.7 17.0 6.2": ["bushwhacking"], "-3.2 10.4 7.0": ["hubbing"], "5.9 0.2 -5.4": ["leafleted"], "1.1 14.1 15.6": ["gulfs"], "-1.8 9.6 10.2": ["tasing"], "14.0 8.1 4.3": ["mudbath"], "2.5 -0.2 10.8": ["kenaf"], "0.1 11.0 14.7": ["prizefighting"], "-4.1 10.6 13.7": ["dones"], "1.1 10.9 10.9": ["exosomes"], "18.9 6.0 12.4": ["wintergreen"], "16.3 4.0 17.6": ["welly"], "3.9 17.4 9.5": ["urushiol"], "6.6 4.0 14.4": ["rooibos"], "17.0 4.1 14.5": ["absently"], "-6.0 1.7 5.2": ["dissappointed"], "0.6 18.8 11.3": ["forechecked"], "13.2 16.9 2.2": ["remold"], "13.7 8.8 4.8": ["unquantified"], "-4.1 10.2 1.2": ["invigilator"], "5.6 -0.2 2.6": ["donator"], "3.0 1.9 7.5": ["ccg"], "13.7 15.9 25.4": ["roos"], "-8.2 11.9 10.9": ["downline"], "13.5 8.5 12.3": ["glacially"], "4.7 8.8 11.7": ["subdomains"], "6.2 3.9 7.0": ["cnet"], "3.1 10.2 7.4": ["cliquey"], "1.3 -0.2 14.9": ["shipbroker"], "13.5 14.0 18.1": ["piddle"], "-3.1 13.3 12.8": ["intermix"], "-3.2 18.6 6.6": ["asana"], "4.7 -5.5 9.8": ["leh"], "6.8 8.4 10.5": ["anatomies"], "2.2 13.5 27.3": ["diatom"], "6.7 7.6 13.2": ["supermoon"], "0.6 12.9 13.7": ["bleeders"], "2.3 3.9 6.1": ["detuned"], "6.1 0.5 7.0": ["canters"], "12.4 4.8 29.6": ["gunwales"], "15.8 13.5 25.5": ["cypresses"], "24.4 11.2 10.7": ["artifical"], "-0.5 -1.2 -0.3": ["rotigotine"], "16.0 22.1 26.2": ["whiteflies"], "-7.5 5.6 7.1": ["nonteaching"], "9.6 6.8 20.2": ["firth"], "6.3 10.1 18.3": ["sieving"], "4.0 10.1 13.5": ["tobacconists"], "7.5 0.3 15.9": ["awa"], "14.4 22.5 8.4": ["verticality"], "10.8 2.4 5.2": ["decidely"], "3.3 14.5 2.7": ["instable"], "-1.5 26.5 1.6": ["sacrificially"], "6.5 3.0 8.8": ["hye"], "8.4 23.3 7.3": ["superego"], "16.5 28.8 12.5": ["boogeymen"], "5.2 11.1 5.9": ["bidets"], "-0.9 6.2 5.6": ["nonparticipating"], "2.5 11.6 10.3": ["doubleplay"], "27.1 1.3 24.7": ["toucan"], "15.9 2.9 1.8": ["axeing"], "2.8 -8.8 14.9": ["permed"], "4.5 12.0 31.9": ["kimchee"], "2.2 -1.6 9.0": ["domainers"], "10.7 11.8 7.6": ["infrasound"], "3.0 19.4 11.7": ["devastations"], "10.0 29.8 6.6": ["tripwires"], "11.5 4.5 4.2": ["savy"], "5.1 -0.2 5.4": ["madams"], "9.4 11.7 6.5": ["sonny"], "6.6 21.6 2.3": ["uncontainable"], "5.5 6.9 11.8": ["drinkability"], "-7.2 6.7 4.5": ["acidosis"], "3.8 17.3 0.2": ["ostracise"], "9.5 6.6 6.4": ["seach"], "-3.5 1.6 8.0": ["declamation"], "-1.8 6.0 12.5": ["alluvium"], "10.0 0.6 32.0": ["celadon"], "6.8 5.5 8.6": ["tera"], "-3.9 12.3 8.5": ["overweighted"], "0.1 7.8 7.7": ["estrogenic"], "0.9 10.7 10.2": ["steelband"], "6.7 8.6 0.9": ["magneto"], "3.9 6.0 11.0": ["fracs"], "-2.7 1.0 26.1": ["deglaze"], "-2.6 3.4 4.0": ["pneumothorax"], "0.3 25.6 5.1": ["fatalist"], "3.2 7.0 23.4": ["overhunting"], "-0.3 3.5 9.2": ["grantmakers"], "10.0 5.9 10.5": ["seismometer"], "-0.0 1.1 11.2": ["renderers"], "2.7 15.6 7.3": ["transmittable"], "6.3 -0.4 15.0": ["kindy"], "-1.0 -1.5 0.2": ["indisposition"], "-4.9 6.9 21.4": ["chondrocytes"], "9.3 8.3 42.4": ["hushpuppies"], "0.2 10.1 9.7": ["accretions"], "2.9 13.1 8.7": ["jaggies"], "6.2 15.5 5.5": ["zigging"], "7.9 3.7 13.4": ["howard"], "11.0 9.7 7.7": ["clusterfuck"], "15.5 5.1 11.3": ["filching"], "-2.8 3.9 11.8": ["nina"], "4.2 2.1 9.1": ["downlinking"], "-0.1 20.0 6.0": ["incrimination"], "2.3 5.0 6.6": ["degreasing"], "2.9 2.6 7.1": ["midland"], "4.6 16.1 9.4": ["dirtiness"], "-1.1 8.5 6.3": ["workholding"], "2.5 7.5 7.5": ["ridaforolimus"], "19.2 2.6 6.3": ["galleria"], "-1.0 20.4 10.3": ["unmixed"], "3.7 -7.7 9.6": ["surrey"], "-1.0 4.5 8.7": ["prostacyclin"], "13.3 6.5 15.3": ["piggish"], "-0.3 12.9 10.8": ["actorly"], "-0.4 2.9 25.2": ["sultanas"], "-1.0 14.6 6.3": ["monetarism"], "3.5 2.8 8.6": ["micros"], "6.8 14.4 6.0": ["chumminess"], "3.5 5.9 6.3": ["glovesman"], "9.3 12.3 12.3": ["kungfu"], "6.6 12.5 8.4": ["codependency"], "3.3 -4.7 -0.8": ["juin"], "-5.4 9.7 6.0": ["securityholder"], "5.6 1.2 31.4": ["longan"], "-6.5 5.9 7.0": ["upconversion"], "4.3 12.0 26.6": ["japonica"], "-2.9 14.0 6.3": ["tsarist"], "10.5 15.2 24.4": ["squaw"], "14.7 6.3 14.6": ["ciggies"], "3.3 2.7 9.0": ["legibly"], "-1.4 0.8 0.6": ["scandium"], "13.4 26.1 10.8": ["xenophobe"], "3.0 4.5 7.7": ["anisotropy"], "18.0 2.9 5.3": ["monikered"], "12.2 11.6 17.0": ["nbc"], "0.4 9.9 6.6": ["harmattan"], "-6.8 7.3 5.7": ["factfinder"], "-6.3 3.0 12.9": ["zin"], "12.0 12.2 10.5": ["industriously"], "5.8 6.5 19.2": ["maxima"], "-6.1 8.4 1.1": ["softeners"], "0.4 17.6 18.2": ["singlehanded"], "6.1 3.5 11.6": ["moldable"], "10.2 3.4 26.9": ["skinks"], "12.8 6.7 9.5": ["corkboard"], "8.6 2.7 16.2": ["melanosomes"], "-14.1 18.6 -2.0": ["mefloquine"], "13.4 17.7 26.5": ["froggy"], "4.8 6.2 9.0": ["drivetime"], "12.8 13.1 11.6": ["cadaverous"], "8.9 4.2 11.6": ["smatterings"], "7.4 22.7 8.7": ["outhustle"], "-16.1 7.7 10.6": ["myelosuppression"], "7.3 14.4 18.4": ["trice"], "11.6 2.4 4.6": ["buckypaper"], "6.1 -4.1 13.7": ["bacchanalian"], "3.7 7.2 8.8": ["quintillion"], "5.5 -7.1 11.1": ["uncashed"], "-0.7 5.3 -2.1": ["mergermarket"], "4.3 13.0 9.1": ["fetter"], "7.5 11.8 3.7": ["absolutley"], "6.7 14.6 10.3": ["spookier"], "11.1 19.7 15.7": ["dropkicked"], "13.6 7.8 9.1": ["supertax"], "13.8 0.5 0.9": ["lis"], "13.9 -1.0 0.7": ["hairbrushes"], "0.8 29.0 10.4": ["instanced"], "4.4 12.9 10.4": ["nanospheres"], "11.5 15.2 8.5": ["whoopin"], "3.4 14.2 -0.9": ["defacements"], "7.5 29.1 15.4": ["countermove"], "1.0 11.5 0.7": ["stylebook"], "3.1 13.8 7.3": ["histograms"], "3.6 6.3 10.6": ["piecework"], "11.6 1.6 19.3": ["fastenings"], "6.0 5.4 13.0": ["songster"], "-4.3 5.4 4.0": ["nonfamily", "biopsychosocial"], "3.5 13.4 9.2": ["inflations"], "4.0 22.6 11.5": ["teabagging"], "16.3 14.6 12.3": ["quicktime"], "4.9 5.6 13.5": ["beguilingly"], "13.3 7.1 6.0": ["swelters"], "8.5 -1.7 2.1": ["alfa"], "3.9 12.5 13.0": ["siltstone"], "10.3 12.0 21.8": ["snapdragon"], "5.6 24.6 9.9": ["allah"], "5.2 5.3 6.5": ["auch"], "1.5 4.1 10.7": ["crocheters"], "-2.4 3.2 5.4": ["babysits"], "-2.6 2.7 0.6": ["polysomnography"], "-3.4 2.2 14.1": ["axonal"], "4.5 27.4 6.5": ["satraps"], "2.4 0.2 7.4": ["reline"], "8.4 10.4 5.2": ["muffles"], "-2.2 9.3 6.8": ["denatured"], "8.9 8.9 9.1": ["schoolbook"], "1.6 17.9 8.0": ["selfhood"], "2.2 4.3 6.5": ["muhurat"], "-5.9 5.8 11.6": ["thiopental"], "-0.9 10.5 4.9": ["uncooled"], "4.3 -3.1 12.5": ["tollgate"], "5.1 30.3 7.1": ["bioweapon"], "0.8 7.3 4.8": ["absconds"], "-1.6 5.1 1.2": ["positiveness"], "9.6 9.6 8.0": ["nightclubbing"], "-1.4 -1.6 4.6": ["functionalized"], "-0.1 -6.0 -0.1": ["microfilmed"], "0.3 -1.9 1.1": ["photodetectors"], "3.7 4.4 23.5": ["baka"], "6.5 8.3 5.5": ["sacral"], "0.8 8.3 14.0": ["hybridisation"], "10.6 0.2 17.9": ["manila"], "8.2 14.0 8.1": ["toadying"], "2.6 12.5 7.8": ["unreconciled"], "10.9 3.8 16.1": ["puddled"], "-0.6 -2.3 11.7": ["hormonally"], "1.5 16.3 6.9": ["unnumbered"], "-1.2 12.9 5.6": ["deregistering"], "11.4 7.1 26.2": ["wineglass"], "-4.5 1.9 -3.5": ["takeback"], "4.7 23.5 18.9": ["sinkerball"], "10.0 2.7 16.7": ["boney"], "18.2 15.1 5.8": ["clambers"], "9.3 13.2 8.3": ["zagging"], "9.9 8.6 25.8": ["seedpods"], "4.1 2.7 15.1": ["curbsides"], "5.6 17.1 12.8": ["bureacracy"], "2.8 5.8 1.0": ["mailout"], "-10.9 5.7 10.9": ["progestins"], "6.2 9.9 17.3": ["uncured"], "5.7 14.3 12.0": ["aftereffect"], "1.1 20.3 -2.2": ["upholder"], "0.2 4.2 9.8": ["dysprosium"], "-3.9 -1.2 9.5": ["nonaffiliated"], "-4.9 -0.0 8.5": ["sforce"], "-1.0 4.4 1.2": ["deeding"], "1.7 0.1 9.8": ["flexographic"], "12.9 8.7 20.2": ["orangey"], "2.5 3.1 11.4": ["subtotal"], "4.5 13.9 8.8": ["fiancees"], "3.2 3.3 12.2": ["folksongs"], "6.1 7.9 1.0": ["arthroscope"], "-2.4 11.3 6.1": ["calypsonian"], "-2.1 6.6 6.0": ["overnighting"], "8.6 7.3 0.9": ["purvey"], "6.6 13.4 4.8": ["retarget"], "7.5 16.6 3.8": ["irresolvable"], "-1.8 -5.3 10.5": ["grandparenting"], "14.3 15.7 13.6": ["whinny"], "-4.9 -4.8 12.4": ["inositol"], "5.2 6.4 12.9": ["lek"], "-3.2 2.9 -5.5": ["hemodynamics"], "4.6 2.8 12.9": ["freestlye"], "9.3 10.1 18.4": ["cerise"], "-1.7 13.1 13.2": ["muchness"], "-5.8 3.4 4.6": ["ridesharing"], "14.1 13.2 16.5": ["bower"], "8.4 8.2 15.3": ["showiest"], "3.2 26.4 2.6": ["theocracies"], "-3.4 -7.6 4.4": ["pubertal"], "-2.8 5.9 15.2": ["homebrewing"], "3.0 7.7 7.4": ["kaffiyeh"], "6.5 2.2 3.4": ["oxy"], "-5.6 14.9 -0.2": ["recurrently"], "-10.5 -3.5 3.0": ["workshopping"], "-2.3 9.8 7.3": ["spendable"], "21.0 0.8 -1.7": ["acqusition"], "3.3 0.8 0.1": ["ateliers"], "1.0 19.6 9.3": ["fermions"], "4.9 15.9 20.1": ["woodsmen"], "4.1 4.2 0.9": ["hydroxy"], "-5.4 6.1 3.4": ["excipient"], "9.1 5.1 18.6": ["resturant"], "-3.8 9.8 4.7": ["stoped"], "11.3 16.9 12.1": ["ritualistically"], "13.6 6.8 16.0": ["piney"], "9.6 20.0 3.1": ["myopically"], "6.6 -1.2 11.2": ["housecleaner"], "1.3 17.9 13.8": ["barrenness"], "11.5 22.9 18.0": ["gatecrasher"], "-4.6 25.0 9.5": ["compromiser"], "2.8 -0.5 5.9": ["compounders"], "2.3 17.1 16.2": ["staphylococcus"], "4.2 9.6 15.9": ["chloroplasts"], "4.9 14.8 5.3": ["ecliptic"], "-4.0 8.0 2.0": ["belived"], "-2.5 1.2 9.9": ["vardenafil"], "0.8 -1.8 -3.4": ["hewas"], "7.6 20.2 8.1": ["archconservative"], "-5.9 4.0 0.8": ["proctored"], "6.0 12.2 12.2": ["beardless"], "-2.8 9.9 9.6": ["intron"], "-2.3 22.6 8.0": ["borderlines"], "2.4 -2.4 5.1": ["photocredit"], "4.9 8.7 5.7": ["stuntwoman"], "9.1 20.3 10.9": ["doughboy"], "-5.5 4.7 9.3": ["titers"], "5.5 8.2 27.1": ["gari"], "14.5 9.4 22.0": ["candleholder"], "8.9 7.4 15.7": ["comcast"], "6.4 9.3 20.2": ["betel"], "-0.1 15.9 6.9": ["foggers"], "-11.4 7.7 6.8": ["grantors"], "19.8 7.1 7.8": ["hucksterism"], "-1.4 -1.0 9.5": ["bec"], "-1.0 8.1 14.5": ["canyoning"], "-1.4 10.7 9.1": ["upshifts"], "12.3 6.7 18.1": ["crumpet"], "2.3 6.4 9.3": ["sk"], "0.4 1.8 6.3": ["sabha"], "16.8 4.8 8.6": ["rustles"], "14.6 4.7 28.1": ["canna"], "-7.0 -0.3 3.3": ["hallmarking"], "0.8 8.1 -4.2": ["interwar"], "7.2 -1.1 2.7": ["steamier"], "-19.1 0.2 4.3": ["inservice"], "4.4 25.0 9.3": ["sodomites"], "1.1 19.1 14.9": ["ablative"], "8.2 1.1 12.7": ["folderol"], "2.2 1.1 5.4": ["allstar"], "-7.6 9.9 3.3": ["diagnosable"], "15.7 7.4 7.8": ["brainiest"], "5.6 4.3 2.6": ["kansas"], "3.8 1.5 12.0": ["pullup"], "10.6 5.7 16.4": ["potties"], "6.8 14.2 10.3": ["bitmaps"], "1.7 11.2 -4.2": ["duplicators"], "10.2 12.6 13.7": ["carhop"], "3.4 13.7 11.1": ["lamplight"], "5.7 9.5 25.6": ["iridescence"], "11.3 22.5 7.9": ["pwned"], "7.0 12.8 15.7": ["steppingstones"], "-1.7 3.2 8.1": ["outgassing"], "7.4 11.2 10.2": ["stoopid"], "1.1 15.0 11.9": ["attainder"], "-3.2 10.0 26.4": ["acidified"], "8.0 16.4 1.7": ["truthers"], "-8.1 6.8 6.8": ["autistics"], "8.0 11.7 17.8": ["pureeing"], "2.4 19.2 7.6": ["unfilmable"], "25.2 20.4 13.4": ["banshees"], "5.2 0.8 1.4": ["wellsite"], "11.9 5.5 2.9": ["scannable"], "14.0 13.7 4.0": ["starless"], "0.0 4.7 8.6": ["glamorization"], "-9.9 -3.9 6.0": ["clerkships"], "18.1 6.2 26.9": ["lengthways"], "2.6 27.2 9.8": ["sepoys"], "5.2 -5.6 -1.3": ["ents"], "18.9 5.8 26.0": ["stripey"], "3.8 15.8 1.9": ["unconcern"], "13.8 10.0 7.9": ["bannister"], "-1.8 15.2 11.8": ["conversationalists"], "-6.1 35.0 14.5": ["polytheists"], "4.6 -2.5 10.9": ["pipelining"], "4.7 2.0 9.8": ["southland"], "4.2 9.7 14.7": ["truculence"], "10.0 13.2 27.0": ["delphiniums"], "20.5 -2.4 -2.8": ["licenser"], "1.6 1.9 11.1": ["acetyl"], "8.0 2.1 10.5": ["buyin"], "17.0 10.9 15.5": ["whoo"], "2.2 17.9 23.4": ["vinca"], "-0.9 17.7 7.8": ["reelecting"], "6.4 1.6 10.9": ["inconclusively"], "7.3 18.6 13.9": ["whuppin"], "-1.4 -4.1 9.5": ["showhouse"], "1.2 9.4 9.1": ["marabout"], "6.5 2.3 5.0": ["sidepods"], "-0.3 2.3 16.8": ["trenchless"], "-5.1 -10.6 2.3": ["tba"], "-4.3 6.4 3.2": ["underinsurance"], "7.0 11.4 15.9": ["supari"], "2.8 -4.2 -1.1": ["annouce"], "7.1 8.5 14.8": ["victoria"], "8.0 0.1 17.5": ["briquette"], "8.6 4.8 12.7": ["palaeontology"], "6.9 -6.4 8.6": ["pah"], "-4.3 13.8 4.8": ["didi"], "11.3 -4.3 19.5": ["plesiosaur"], "-0.9 2.1 0.6": ["semimonthly"], "2.3 0.9 9.0": ["toi"], "-5.5 5.8 8.9": ["djs"], "3.2 14.0 5.3": ["bama"], "-2.4 14.2 6.8": ["flammables"], "11.3 13.9 22.2": ["soaker"], "12.2 -3.5 8.7": ["sul"], "10.5 2.4 7.5": ["pristinely"], "9.0 6.1 7.2": ["stiles"], "2.5 -2.8 6.4": ["nero"], "5.9 17.8 9.1": ["ninny"], "5.8 13.9 14.0": ["dynamites"], "3.3 -6.2 -1.5": ["rn"], "20.8 -0.0 20.3": ["frilled"], "-8.3 15.1 7.9": ["regionalist"], "-4.4 6.6 9.0": ["genotypic"], "17.4 3.2 9.0": ["splashiest"], "7.0 6.4 15.0": ["num"], "7.1 13.5 13.6": ["squibber"], "-9.2 5.9 -3.3": ["azacitidine"], "3.8 9.4 7.0": ["thanx"], "12.3 2.1 5.6": ["panaceas"], "0.8 -7.7 8.8": ["debs"], "3.3 3.7 18.8": ["slowish"], "2.0 12.6 8.5": ["resurge"], "8.7 24.1 25.2": ["stoats"], "5.5 3.7 22.1": ["salamis"], "7.1 4.7 35.0": ["gruyere"], "0.9 17.5 6.2": ["unlearning"], "13.2 17.6 14.6": ["bleepin"], "11.4 8.4 11.2": ["skyways"], "3.0 17.6 3.6": ["obfuscates", "metastasised"], "0.1 -1.2 13.8": ["pantos"], "10.1 4.5 9.3": ["esoterica"], "9.2 8.0 8.9": ["gracias"], "-1.7 8.9 1.7": ["contextualizing"], "5.8 6.2 7.1": ["ssa"], "2.5 23.1 4.2": ["neoliberals"], "-6.5 8.2 15.1": ["overstocks"], "4.7 22.4 14.3": ["kaffir"], "21.0 4.4 19.8": ["scratchers"], "-17.5 -0.9 9.5": ["reversions"], "5.3 9.2 5.9": ["stormer"], "-2.5 8.4 12.9": ["clades"], "-0.4 2.3 3.3": ["cpht"], "18.2 6.3 16.2": ["lattices"], "4.8 12.9 5.0": ["accountholder"], "19.2 11.8 15.6": ["bellyful"], "8.3 17.3 12.0": ["topdown"], "-5.5 18.2 3.6": ["antislavery"], "13.1 14.3 17.9": ["flagella"], "19.7 12.7 26.3": ["housecat"], "-5.2 2.3 5.3": ["diplomate"], "16.8 4.3 18.7": ["barrell"], "22.5 14.8 28.1": ["tendril"], "-10.2 10.5 9.6": ["zonings"], "15.7 9.8 2.6": ["choirboys"], "7.5 9.1 3.3": ["unflatteringly"], "24.1 5.7 6.8": ["wallahs"], "14.1 6.3 18.6": ["smackers"], "-4.4 2.0 4.2": ["vulvar"], "6.4 11.4 7.6": ["timelessly"], "3.8 4.9 5.9": ["prefight"], "0.8 12.2 6.8": ["interrelate"], "10.1 8.3 12.2": ["fortunetellers"], "0.4 1.3 3.7": ["fb"], "6.6 4.1 10.5": ["tradies"], "-5.9 7.9 6.9": ["crimestoppers"], "18.1 6.4 16.9": ["derrieres"], "17.5 6.1 8.4": ["sugarplums"], "5.6 9.4 4.9": ["licencee"], "-2.0 14.0 -4.6": ["unstintingly"], "-0.8 20.2 15.9": ["cultivable"], "18.2 10.6 5.4": ["svengali"], "2.6 10.1 8.7": ["muons"], "9.0 2.0 10.0": ["recapitalisations"], "9.5 8.4 7.8": ["handgrip"], "13.6 7.6 25.7": ["baldy"], "22.1 17.6 11.2": ["dweebs"], "-5.3 10.6 15.1": ["tings"], "5.0 22.3 -2.3": ["calumnies"], "10.8 5.6 9.9": ["puppeteering"], "-1.0 -1.7 8.9": ["amenability"], "8.4 9.0 26.5": ["fireboats"], "1.9 -3.0 7.6": ["osteopaths"], "-7.2 -4.3 13.3": ["tos"], "2.6 3.3 12.7": ["midvalley"], "16.0 -0.9 10.7": ["velveteen"], "10.4 9.6 26.5": ["buckeyes"], "6.7 5.9 10.5": ["stomached"], "-0.1 7.9 5.5": ["ecard"], "2.9 18.0 15.1": ["rodenticides"], "4.5 5.3 37.2": ["laksa"], "-0.4 4.9 15.2": ["cartage"], "4.9 11.7 11.5": ["plavix"], "-9.0 12.8 12.6": ["intermarry"], "-5.1 5.8 6.4": ["blepharitis"], "-2.0 7.4 8.1": ["moisturizes"], "5.7 4.4 3.1": ["modularized"], "10.0 13.1 1.1": ["propagator"], "-0.8 13.0 1.5": ["abrogates"], "10.4 19.1 5.2": ["denuding"], "12.0 10.7 8.7": ["whaddya"], "4.1 26.6 11.9": ["sneakier"], "21.9 8.6 19.9": ["washtub"], "8.1 19.7 11.5": ["artfulness"], "11.7 18.0 12.9": ["eyepatch"], "-6.1 6.3 45.5": ["salmonids"], "2.4 10.3 13.5": ["torres"], "0.8 11.4 20.8": ["rehabilitator"], "5.1 -11.0 12.1": ["ballgowns"], "-4.3 0.9 3.2": ["seva"], "-0.3 19.7 10.4": ["martinet"], "11.2 3.4 9.3": ["duopolies"], "3.2 2.2 6.9": ["volcanology"], "-3.8 0.3 16.3": ["ferrosilicon"], "12.2 2.0 0.1": ["internationalising"], "2.3 29.0 6.7": ["irredentist"], "-0.8 4.1 11.4": ["laminin"], "-2.7 11.4 7.0": ["redenomination"], "1.2 17.7 2.0": ["cryptology"], "24.2 0.7 -1.5": ["supremos"], "-3.4 4.0 3.1": ["chromatographic"], "0.7 10.0 5.7": ["fibrotic"], "2.2 8.2 6.1": ["rainwear"], "2.7 5.2 6.3": ["oboes"], "12.0 2.6 21.3": ["rasta"], "1.4 6.7 14.8": ["bentgrass"], "4.7 0.8 15.7": ["cheng"], "5.8 12.4 13.6": ["wisdoms"], "-9.1 3.8 6.5": ["parietal"], "5.6 22.2 11.6": ["eurosceptics"], "-3.4 10.2 16.1": ["loosies"], "2.2 3.9 11.7": ["naughtier"], "-6.3 6.6 29.7": ["flyfishing"], "6.1 10.8 26.0": ["mallow"], "-0.7 -1.1 8.1": ["motherhouse"], "3.2 0.9 12.5": ["nibs"], "9.1 9.4 27.6": ["lunchmeat"], "7.8 7.5 9.3": ["narthex"], "-2.6 11.6 10.6": ["ifosfamide"], "3.7 11.8 1.5": ["posible"], "-3.9 13.6 12.0": ["laudably"], "7.3 9.1 24.3": ["horseflesh"], "-5.2 6.8 5.5": ["crosschecked"], "-9.5 9.9 7.0": ["uncontroverted"], "1.2 7.3 7.2": ["kanban"], "12.1 11.5 8.6": ["loungeroom"], "-1.7 1.1 2.9": ["dux"], "12.1 10.2 9.7": ["echoey"], "24.4 7.5 10.1": ["supermajors"], "-1.0 12.7 9.2": ["inheritable"], "-0.1 19.7 9.0": ["disputation"], "0.9 8.3 7.9": ["naughtiest"], "7.8 14.4 14.2": ["midbrain"], "-0.7 -4.3 8.6": ["corsetry"], "6.2 6.2 8.0": ["transmigration"], "1.2 15.4 -7.8": ["organisationally"], "1.9 8.2 7.1": ["reforesting"], "5.5 4.0 18.2": ["woodturning"], "13.6 13.2 9.7": ["motorola"], "4.9 3.0 11.5": ["weatherboard"], "-1.8 3.0 3.5": ["optionholders"], "2.9 4.8 -4.8": ["minibars"], "7.8 24.6 5.5": ["coloniser"], "0.6 4.5 7.5": ["duetting"], "7.6 1.4 0.5": ["dti"], "3.7 6.0 37.8": ["mariculture"], "3.4 5.5 8.9": ["cantinas"], "8.7 17.2 13.8": ["moonshiner"], "8.0 1.3 15.3": ["unfed"], "3.4 3.0 12.6": ["gasline"], "2.9 -2.5 5.4": ["regraded"], "5.5 -5.9 4.5": ["lon"], "-10.9 12.2 3.2": ["nonresponders"], "-1.6 14.8 12.4": ["imidacloprid"], "17.4 5.3 24.0": ["gherkins"], "6.5 11.1 6.0": ["tumultous"], "10.0 15.4 29.2": ["dropshot"], "11.1 4.3 7.4": ["jubilance"], "-1.2 14.3 0.1": ["rechargeables"], "-9.0 -2.9 5.3": ["disenrolled"], "6.6 15.6 3.4": ["snoopy"], "6.4 13.3 -0.7": ["embarrasment"], "19.4 17.0 4.9": ["industrialism"], "13.6 17.5 5.1": ["handiest"], "-0.2 11.4 25.4": ["forbs"], "-1.1 9.6 4.6": ["darusentan"], "6.3 28.8 4.7": ["destablise"], "9.9 -2.7 20.7": ["ibex"], "-0.1 4.7 13.6": ["reattachment"], "12.5 6.3 13.3": ["hecklerspray"], "-0.9 -2.5 11.8": ["tattooists"], "14.6 17.3 10.9": ["banzai"], "-11.6 7.7 -4.8": ["prehospital"], "5.3 13.3 12.8": ["genuflection"], "2.9 20.9 7.5": ["psychotics"], "8.5 8.6 -0.7": ["flagellation"], "17.2 4.9 10.5": ["overexpansion"], "13.1 2.6 -1.7": ["keyrings"], "15.5 5.5 13.1": ["pooh"], "9.9 9.5 8.6": ["nuttiest"], "-1.2 5.2 13.4": ["reinitiate"], "4.5 6.2 8.6": ["reversibly"], "1.2 21.2 3.8": ["fuze"], "16.0 16.5 10.2": ["voracity"], "14.6 15.1 22.8": ["portside"], "17.1 14.7 14.0": ["trackless"], "1.0 4.8 12.3": ["nate"], "18.3 5.0 12.5": ["unrolls"], "11.5 -3.6 6.1": ["zippier"], "-0.2 0.9 18.7": ["teff"], "6.7 8.0 18.6": ["polytunnels"], "1.6 7.0 15.7": ["messin"], "9.9 2.8 4.5": ["mailmen"], "-5.7 -1.5 3.9": ["prenatally"], "3.0 -2.4 9.5": ["petites"], "7.3 9.5 0.2": ["breakthough"], "10.7 8.7 21.1": ["woodblock"], "7.8 3.1 0.5": ["preloading"], "6.4 8.7 7.0": ["domesticating"], "-0.2 5.3 6.7": ["atones"], "5.6 6.1 20.3": ["arepas"], "-0.3 7.4 28.5": ["mezze"], "1.2 19.8 9.8": ["shabiha"], "-4.6 -0.2 7.3": ["sleepier"], "6.3 1.5 15.0": ["maha"], "5.1 11.0 13.6": ["amor"], "3.1 12.3 9.9": ["bewilders"], "12.5 18.8 7.6": ["postapocalyptic"], "11.6 6.0 -0.7": ["injuction"], "-8.0 11.8 5.5": ["noradrenaline"], "8.2 8.8 11.4": ["netflix"], "-1.6 0.7 7.8": ["colourist"], "9.0 13.0 8.2": ["begrudges"], "7.2 6.5 8.3": ["cmd"], "-1.6 -1.7 2.5": ["guidances"], "-4.8 9.7 3.4": ["emolument"], "0.3 -3.4 10.1": ["wallcoverings"], "9.0 9.4 8.5": ["bumpin"], "19.0 2.6 19.2": ["nubby"], "13.3 10.4 23.1": ["icecap"], "-0.3 1.0 17.2": ["balusters"], "7.5 -1.7 29.8": ["cornflour"], "-5.2 10.8 6.0": ["nilotinib"], "10.7 5.5 27.7": ["midden"], "6.8 7.1 12.6": ["ascetics"], "10.3 8.8 12.4": ["folkways"], "13.7 -3.5 19.7": ["ribboned"], "6.4 5.0 13.8": ["discoloring"], "14.8 7.5 20.0": ["moccasin"], "15.6 18.3 15.3": ["bushman"], "15.5 9.4 1.1": ["moneyman"], "7.8 -3.4 3.4": ["reacceleration"], "16.6 1.4 27.5": ["pebbly"], "-5.1 8.6 9.3": ["autoloader"], "5.3 9.7 4.2": ["bopper"], "6.7 2.5 4.9": ["tru"], "5.4 6.8 6.9": ["excavates"], "-0.8 -2.1 3.2": ["interlining"], "8.0 6.0 19.9": ["timbales"], "9.3 0.1 1.3": ["popularisation"], "13.3 7.4 15.0": ["salaryman"], "20.8 10.1 1.2": ["ification"], "-3.8 14.3 4.5": ["agitational"], "10.2 25.2 18.8": ["laydown"], "-3.9 7.1 15.4": ["junkers"], "6.7 3.0 5.8": ["frescoed"], "6.8 8.4 4.9": ["impregnates"], "4.6 14.0 13.1": ["subfreezing"], "4.4 17.1 3.8": ["boastfully"], "13.1 6.9 24.8": ["kauri"], "8.2 7.0 4.3": ["altho"], "3.6 5.4 1.8": ["fitments"], "18.2 3.8 17.0": ["dangly"], "-1.0 14.5 9.2": ["protestants"], "9.0 8.3 -1.3": ["glamorising"], "13.5 7.8 8.8": ["ooohs"], "0.6 1.5 7.2": ["crochets"], "4.4 11.5 23.8": ["charcoals"], "7.9 14.4 11.2": ["anticyclone"], "4.7 8.6 -12.0": ["disclaiming"], "5.6 16.3 21.8": ["limpet"], "3.0 19.2 6.4": ["centralism"], "5.1 17.4 12.3": ["plinking"], "3.2 11.5 -3.0": ["libelled"], "-0.8 3.0 1.0": ["resp"], "8.3 10.2 12.1": ["climategate"], "4.7 10.4 3.5": ["lensmen"], "-1.7 17.0 12.3": ["rootedness"], "0.4 6.0 5.6": ["gatekeeping"], "7.0 15.5 3.3": ["coddles"], "-5.4 9.1 -0.7": ["ulemas"], "0.0 2.0 7.1": ["shedrow"], "7.2 12.4 8.4": ["magnetar"], "-7.1 5.9 2.7": ["nonconsecutive"], "4.9 11.4 10.6": ["hyperspectral"], "-0.1 10.0 6.7": ["thos"], "8.3 10.3 33.1": ["wigglers"], "3.7 11.6 6.8": ["convolution"], "0.4 4.3 15.2": ["basalts"], "8.1 8.9 14.4": ["kita"], "2.2 1.0 5.7": ["bodykit"], "3.2 -0.4 8.4": ["spritzed"], "13.2 7.2 2.2": ["centrefold"], "-5.2 0.1 23.9": ["muscat"], "2.3 -5.5 13.1": ["monoprints"], "-0.6 6.0 16.0": ["dhotis"], "6.0 0.6 6.5": ["uncertainity"], "8.4 15.9 10.9": ["cybercrooks"], "12.8 10.8 16.1": ["doomy"], "5.0 7.6 18.8": ["sheltie"], "-3.3 0.2 10.7": ["handbell"], "7.1 18.5 9.0": ["fangirl"], "12.2 3.8 7.7": ["straggle"], "4.7 12.3 18.1": ["cowherd"], "-1.3 4.0 18.5": ["lehenga"], "-7.3 3.6 8.9": ["deaconess"], "-0.1 5.4 11.9": ["sculler"], "-1.1 10.0 6.7": ["perineum"], "-2.8 20.3 4.5": ["excludable"], "8.3 3.9 12.5": ["turnings"], "7.5 13.0 16.4": ["carouse"], "-13.3 9.5 10.7": ["backgrounding"], "19.1 4.6 20.8": ["salarymen"], "-9.2 7.1 11.4": ["wellfield"], "7.8 2.5 11.9": ["geekier"], "1.3 13.8 11.4": ["tonalities"], "4.0 5.1 7.8": ["potentiometers"], "-1.1 18.4 18.6": ["runbacks"], "4.9 13.7 -2.3": ["ranker"], "-9.4 5.5 6.4": ["interments"], "2.4 11.3 8.9": ["sinusoidal"], "10.7 3.6 -1.1": ["multilane"], "-4.4 13.8 3.8": ["victimology"], "5.0 -2.9 10.7": ["tanezumab"], "5.1 14.6 11.9": ["unanchored"], "3.9 34.2 12.1": ["backstab"], "0.7 12.3 13.7": ["overspray"], "3.6 5.4 14.8": ["marquetry"], "10.3 7.3 7.2": ["chennai"], "8.3 20.8 5.7": ["devasting"], "5.3 19.0 3.5": ["multiculturalists"], "4.0 3.9 14.4": ["tobacconist"], "3.0 3.1 6.6": ["payslip"], "-10.1 12.8 21.6": ["headwater"], "22.8 3.5 -1.7": ["emblazon"], "1.6 5.6 20.0": ["rootstocks"], "-8.7 13.4 6.7": ["countermand"], "-0.7 5.3 8.9": ["luminal"], "9.6 12.1 7.9": ["warier"], "9.1 10.5 9.8": ["fortes"], "12.6 4.9 16.5": ["settees"], "3.3 12.7 14.0": ["letterboxing"], "4.9 4.8 21.5": ["icepack"], "5.5 9.3 31.8": ["grebes"], "-2.9 -0.9 2.9": ["emerita"], "-2.9 9.4 15.3": ["rainless"], "9.4 10.2 8.1": ["jink"], "21.8 12.8 13.5": ["phantasmagoric"], "9.0 5.2 4.8": ["cuing"], "1.0 7.7 9.1": ["rae"], "-3.5 2.5 15.4": ["chalcocite"], "3.8 26.8 0.8": ["delegitimizing"], "3.7 -6.4 5.8": ["renumeration"], "6.9 8.3 14.8": ["nanosilver"], "5.5 10.8 4.5": ["outspends"], "-0.6 -0.1 9.4": ["mailbags"], "2.7 3.0 2.9": ["spe"], "9.0 -1.1 6.4": ["headier"], "19.6 11.0 8.9": ["breadbox"], "0.4 23.0 1.7": ["agaist"], "7.9 9.3 7.8": ["rath"], "13.3 13.3 22.6": ["gyre"], "2.6 8.7 1.1": ["firewalling"], "6.7 18.5 32.6": ["chickweed"], "4.4 19.8 14.4": ["microcosms"], "11.1 11.4 15.6": ["tamping"], "-3.0 3.5 18.7": ["canoers"], "5.9 -4.8 9.0": ["overbudget"], "-1.1 15.9 0.8": ["torsional"], "-5.5 3.1 50.0": ["scalloping"], "13.4 15.9 10.7": ["emptiest"], "-0.8 16.1 4.7": ["homoeroticism"], "15.5 0.9 4.6": ["microcomputers"], "-4.8 6.0 5.9": ["milliohms"], "4.5 4.6 27.7": ["perogies"], "-5.6 17.2 10.4": ["dignities"], "2.9 19.1 8.6": ["pollutions"], "5.1 2.7 23.5": ["hocks"], "-5.5 6.5 9.3": ["metacarpal"], "2.5 9.5 3.4": ["wardriving"], "5.3 16.3 8.5": ["dystopic"], "-5.2 16.9 -3.2": ["incorruptibility"], "7.2 6.4 -0.4": ["molests"], "4.7 4.3 20.8": ["shoestrings"], "-0.0 9.6 16.7": ["offspin"], "5.5 8.7 7.9": ["garlanding", "holmium"], "3.6 9.7 29.3": ["trophic"], "4.7 6.4 9.3": ["severable"], "-1.7 -2.3 4.9": ["colloids"], "-2.3 8.5 5.1": ["crosschecking"], "6.4 4.6 13.1": ["hin"], "2.7 5.5 -3.2": ["duplicator"], "-2.0 4.7 2.0": ["effusions"], "0.9 10.3 6.5": ["pedagogue"], "21.1 9.9 13.8": ["golliwog"], "3.2 4.5 2.0": ["synthase"], "-6.2 2.0 8.1": ["menstruate"], "-6.0 12.3 -0.1": ["effectuating"], "1.6 10.8 5.5": ["liberality"], "-0.7 5.9 4.3": ["sexpert"], "8.0 10.0 3.9": ["skylarking"], "-6.1 2.5 6.2": ["lieder"], "-0.4 8.1 3.3": ["countires"], "-1.2 10.2 2.6": ["referent"], "5.0 2.8 22.0": ["cakey"], "5.3 11.9 8.8": ["rotoscoping"], "7.0 14.5 3.9": ["telegraphic"], "9.1 9.8 23.8": ["atlatl"], "16.2 11.1 9.4": ["clanks"], "-3.3 7.2 -0.4": ["airshows"], "-0.7 0.4 0.5": ["retreaded"], "13.9 4.9 -1.8": ["banka"], "4.5 15.4 11.9": ["equinoxes"], "11.3 7.6 16.3": ["biome"], "0.2 25.9 12.8": ["gunrunners"], "0.9 5.9 2.5": ["revalidate"], "8.6 24.2 6.4": ["persuader"], "18.0 2.7 8.8": ["bellying"], "-3.9 10.9 -1.9": ["hypermiling"], "2.8 -2.4 4.2": ["pmat"], "-2.0 15.1 6.5": ["subds"], "19.6 4.4 6.9": ["retrenches"], "12.0 14.0 8.9": ["indexer"], "6.6 4.9 17.5": ["mani"], "15.8 7.9 8.1": ["glowsticks"], "4.8 18.0 8.3": ["autopilots"], "8.1 10.3 10.6": ["gangways"], "-6.1 12.5 4.9": ["religiousness"], "10.3 30.5 11.5": ["vanquishes"], "0.6 0.6 5.0": ["quints"], "11.2 14.9 12.5": ["crikey"], "-1.7 3.6 5.1": ["finetuning"], "7.2 17.0 9.2": ["outjump"], "9.1 3.0 2.4": ["alterna"], "0.7 12.0 19.3": ["genoa"], "12.4 11.5 51.1": ["bivalve"], "8.3 21.8 2.1": ["hellholes"], "-6.6 4.4 2.8": ["toolchain"], "-1.6 8.5 14.7": ["mellowness"], "-2.5 13.5 3.6": ["backchannel"], "10.9 9.7 21.6": ["quarterhorse"], "-1.2 15.2 7.5": ["substorms"], "10.4 18.4 12.0": ["madden"], "6.5 16.8 10.8": ["overregulated"], "-4.8 4.3 7.0": ["adjudge"], "23.4 -3.5 10.3": ["squeezable"], "-5.5 11.0 0.2": ["contextualise"], "9.2 3.2 8.4": ["freeview"], "7.8 7.4 13.9": ["wishbones"], "7.9 8.1 7.3": ["superblock"], "15.1 4.4 16.1": ["lubed"], "-10.4 3.9 7.1": ["gether"], "6.5 12.2 9.0": ["sidestreets"], "1.6 2.7 29.9": ["workboats"], "-1.0 3.3 8.0": ["hazier"], "0.4 13.4 2.2": ["dnt"], "16.1 0.6 8.1": ["scotching"], "12.0 14.1 10.7": ["encasement"], "4.5 18.6 6.9": ["overextension"], "22.7 7.6 8.3": ["buckyball"], "6.8 4.6 3.7": ["ahhhh"], "10.4 1.2 6.1": ["ween"], "-6.8 20.1 6.7": ["bactericidal"], "2.9 9.5 -0.5": ["theoretic"], "12.2 15.5 4.5": ["holies"], "21.9 10.3 6.5": ["megaplexes"], "4.3 10.5 9.6": ["bullcrap"], "-4.1 11.5 4.0": ["multifocal"], "11.3 10.1 19.9": ["wigwam"], "12.1 9.6 20.9": ["sawgrass"], "-2.4 7.6 12.4": ["lockets"], "0.7 9.8 28.0": ["corms"], "6.5 10.7 34.8": ["waxworms"], "3.5 13.0 7.6": ["suavely"], "1.1 8.2 13.7": ["sharrows"], "3.6 15.2 10.1": ["politicizes"], "-1.0 4.2 20.1": ["carbofuran"], "-7.9 7.7 -6.5": ["familiy"], "-8.8 5.2 14.3": ["badla"], "5.4 12.4 12.2": ["subnotebook"], "4.3 9.8 29.5": ["teppanyaki"], "5.4 6.4 6.6": ["megahits"], "3.1 9.6 9.2": ["tinseltown"], "7.5 6.5 20.0": ["redbuds"], "0.8 -4.4 6.2": ["drycleaners"], "5.6 6.2 10.8": ["chul"], "-0.2 14.0 2.3": ["immediatley"], "22.4 21.7 19.3": ["snakelike"], "1.3 6.9 3.3": ["untelevised"], "9.5 8.8 6.6": ["acquisitiveness"], "5.7 2.3 37.9": ["escargots"], "-5.9 -3.5 4.0": ["neurodevelopment"], "25.4 11.4 24.9": ["biped"], "7.2 8.9 3.4": ["venerating"], "1.1 19.9 8.7": ["mideast"], "2.3 0.2 23.8": ["milksolids"], "6.4 13.2 6.2": ["microtransaction"], "7.8 9.1 4.8": ["scrummed"], "24.7 -1.8 2.1": ["quintupling"], "10.7 9.4 -4.0": ["synchronises"], "1.3 9.1 10.0": ["setlists"], "0.9 8.2 6.0": ["monitory"], "-5.4 7.6 23.0": ["lavenders"], "7.8 -0.6 19.1": ["cablers"], "8.8 -1.4 12.1": ["slighty"], "14.0 4.0 7.9": ["felts"], "12.9 7.8 17.9": ["gangmaster"], "4.7 20.7 32.2": ["killdeer"], "10.2 5.4 2.7": ["sicced"], "1.4 14.4 3.9": ["iterating"], "4.5 9.2 14.9": ["diverters"], "0.6 5.8 9.4": ["mantos"], "4.4 12.4 5.9": ["overstimulation"], "-3.1 7.6 3.5": ["fragilities"], "4.5 2.1 0.9": ["bmp"], "19.7 9.1 23.6": ["tyrannosaur"], "1.7 7.4 9.1": ["fingolimod"], "23.1 12.1 12.8": ["snuffling"], "10.8 9.6 4.4": ["fadeout"], "0.4 0.2 -1.3": ["iheartradio"], "-5.1 5.3 6.8": ["laparoscopically"], "16.3 26.6 7.0": ["waffler"], "19.3 -1.5 9.7": ["truckstop"], "-2.2 18.9 0.5": ["hatemonger"], "-0.5 6.4 -1.1": ["beamline"], "0.5 11.4 6.9": ["immunodeficiency"], "21.1 13.0 25.3": ["melty"], "15.0 8.1 10.1": ["strew"], "9.7 10.5 6.3": ["deodorizing"], "9.0 16.7 14.2": ["inscrutability"], "18.5 15.5 5.2": ["satelite"], "-0.5 17.0 5.2": ["enjoyments"], "2.7 4.8 20.5": ["patta"], "-5.5 26.3 0.8": ["fireground"], "0.5 19.0 -0.3": ["parapsychology"], "1.7 9.1 1.7": ["systematize"], "7.7 10.7 8.8": ["molecularly"], "5.0 3.3 26.9": ["pakoras"], "6.1 10.7 4.7": ["wavefront"], "3.0 5.6 11.7": ["gorings"], "5.2 3.2 14.4": ["unhealthier"], "5.6 -0.3 6.7": ["troughed"], "3.9 5.8 7.9": ["itelligence"], "6.0 13.4 4.3": ["commoditizing"], "1.0 10.9 9.4": ["climatically"], "-4.3 18.3 5.2": ["portrayer"], "-4.8 6.2 1.3": ["perspicacious"], "17.0 22.2 18.8": ["enchantress"], "7.8 2.6 11.4": ["gigolos"], "10.4 5.8 13.7": ["enamelled"], "-7.4 8.7 10.0": ["urs"], "4.7 5.0 7.0": ["wav"], "-7.6 0.8 10.0": ["peritoneal"], "1.8 8.3 6.1": ["centreline"], "-6.4 19.6 7.4": ["airmanship"], "-1.8 18.5 6.1": ["methicillin"], "3.5 6.2 13.7": ["brecciation"], "3.5 3.6 1.7": ["unenthused"], "0.6 6.1 9.5": ["recompetes"], "5.0 10.7 4.9": ["mayorships"], "15.8 0.3 1.3": ["nex"], "12.1 9.4 9.0": ["ohhh"], "-3.8 8.3 9.5": ["rewatching"], "-2.5 3.9 12.4": ["rheumatoid"], "9.8 8.9 7.3": ["withe"], "3.8 -1.7 13.8": ["anganwadi"], "-0.6 4.0 2.6": ["ioimage"], "7.8 3.2 14.2": ["atlanta"], "11.0 6.4 14.3": ["hotrod"], "7.0 8.2 10.7": ["bonjour"], "5.0 6.0 14.6": ["midpoints"], "7.0 2.3 33.4": ["pupusas"], "20.0 15.3 11.0": ["torus"], "0.3 31.0 6.6": ["generalship"], "-2.8 -9.8 7.1": ["frontload"], "10.3 17.0 5.3": ["unsuspectingly"], "1.5 2.5 -3.5": ["affaires"], "9.8 18.5 29.8": ["crabapple"], "0.4 12.4 -4.9": ["everday"], "16.3 6.9 4.7": ["tramways"], "10.0 4.5 6.7": ["alan"], "18.8 18.4 13.9": ["sleazebag"], "-6.1 -1.1 43.9": ["broodstock"], "23.8 11.2 32.5": ["gumball"], "-0.4 5.7 1.5": ["nonuse"], "1.6 5.7 14.3": ["shandy"], "-2.3 1.3 12.3": ["lekgotla"], "4.7 8.7 8.7": ["undershorts"], "3.3 -1.0 13.9": ["nightdress"], "-7.8 0.8 1.8": ["psychomotor"], "5.0 11.5 -5.2": ["weaseled"], "13.1 1.9 9.5": ["fy"], "13.9 20.9 10.4": ["capitulates"], "7.2 7.8 16.8": ["mommas"], "-1.9 1.1 6.2": ["mountainbike"], "3.4 2.0 1.9": ["brominated"], "3.7 7.3 3.0": ["batts"], "6.8 5.0 20.1": ["umber"], "-12.1 0.9 4.0": ["umrah"], "19.5 8.4 0.1": ["businesss"], "-6.9 17.2 9.2": ["foodborne"], "3.0 18.0 4.9": ["punking"], "2.2 -0.1 3.2": ["ame"], "4.7 4.9 12.3": ["headworks"], "-3.7 6.0 10.2": ["nondisabled"], "-7.0 16.0 7.6": ["kickouts"], "-2.2 0.4 5.2": ["crofelemer"], "5.6 1.4 22.3": ["packinghouses"], "5.8 20.7 13.6": ["bounder"], "-1.4 5.9 11.3": ["germline"], "11.2 11.1 39.9": ["rookeries"], "5.0 11.9 20.8": ["worrywart"], "19.9 5.4 3.1": ["electroluminescent"], "2.0 7.2 11.4": ["vocab"], "-5.8 2.2 10.4": ["fortepiano"], "8.0 11.2 12.0": ["oracular"], "16.4 3.2 19.6": ["frappe"], "6.4 1.0 3.5": ["yeard"], "-0.3 8.2 5.8": ["discernibly"], "8.2 13.4 28.6": ["lungfish"], "2.2 0.5 16.3": ["sab"], "7.1 13.7 7.7": ["surpise"], "2.2 16.2 -0.8": ["votary"], "15.5 5.2 17.8": ["kaleidoscopes"], "1.9 11.2 31.8": ["peafowl"], "0.7 13.8 3.0": ["provably"], "1.1 11.1 8.3": ["dueting"], "7.7 -3.6 8.7": ["thesecond"], "-4.2 5.6 4.4": ["typ"], "-3.6 4.2 6.0": ["parallelization"], "10.8 6.4 11.4": ["distribs"], "17.3 17.0 19.9": ["ursine"], "5.5 7.2 10.3": ["britney"], "3.4 3.4 5.3": ["tomorow"], "4.2 5.9 4.7": ["plaudit"], "0.8 -8.1 5.5": ["fouryear"], "12.1 5.2 19.4": ["pukka"], "9.5 2.6 6.2": ["saddlebag"], "5.1 10.4 10.7": ["shamanistic"], "7.7 4.4 31.9": ["streusel"], "12.8 -1.1 9.4": ["microlender"], "-5.5 5.3 11.1": ["snocross"], "24.5 18.6 15.5": ["geddit"], "3.3 -1.2 -0.0": ["ane"], "24.0 -0.9 8.4": ["yoyo"], "8.3 15.1 14.9": ["whipsawing"], "-0.8 9.8 1.9": ["categoric"], "-2.8 14.6 5.0": ["purposive"], "14.7 2.1 -1.7": ["pitchwoman"], "9.8 8.3 7.8": ["pentacle"], "4.7 2.0 18.1": ["chemise"], "4.5 7.6 19.8": ["refrozen"], "3.0 -1.6 2.4": ["microtechnology"], "16.4 8.8 19.5": ["moppet"], "-1.0 16.4 11.0": ["bronchi"], "-5.1 5.3 -1.2": ["softspoken"], "0.6 8.3 7.7": ["exasperates"], "1.6 11.9 3.9": ["intoxicate"], "5.4 6.4 -0.5": ["opps"], "5.2 5.1 9.4": ["homegirl"], "-8.7 0.6 0.7": ["notarization"], "3.2 12.3 10.1": ["cliquish"], "2.4 14.2 8.7": ["newspeople"], "-7.2 1.5 10.8": ["cellaring"], "6.2 4.4 16.5": ["summerhouse"], "13.6 7.7 0.5": ["berlin"], "2.9 7.8 8.8": ["overpromised"], "11.4 7.8 12.0": ["cabooses"], "11.3 0.8 13.8": ["paining"], "7.8 12.6 4.4": ["burried"], "5.2 5.3 13.9": ["haemorrhoids"], "1.7 6.6 16.0": ["tippling"], "6.6 18.2 13.1": ["scattergun"], "6.4 13.5 12.1": ["frazzle"], "3.4 1.5 9.0": ["pushbuttons"], "5.8 1.5 2.0": ["presidente"], "12.4 14.6 23.5": ["jawbreaker"], "2.3 8.7 10.9": ["hybridizing"], "2.0 24.7 5.0": ["umma"], "-7.8 10.7 6.2": ["nallah"], "10.9 13.9 12.1": ["bys"], "7.4 15.3 5.2": ["detrimentally"], "3.6 1.8 8.9": ["ging"], "-3.0 14.6 1.2": ["jizya"], "9.7 15.3 14.8": ["peeper"], "-9.0 7.2 -2.5": ["antithrombotic"], "8.7 18.6 -0.0": ["uncustomary"], "4.8 14.5 30.2": ["lunkers"], "-0.4 14.5 5.5": ["intellectualize"], "8.6 27.8 21.0": ["cutworms"], "-1.5 6.7 23.6": ["arhar"], "3.6 4.5 4.7": ["supertitles"], "-2.3 13.4 8.9": ["electeds"], "6.3 2.9 1.4": ["whinged"], "-4.4 17.0 23.5": ["tippet"], "-8.5 4.1 3.4": ["coeducation"], "2.6 11.4 17.5": ["carnality"], "8.1 15.1 14.5": ["maidservant"], "-5.4 10.5 -9.4": ["mentionable"], "16.6 11.7 11.9": ["toolmaking"], "-3.2 0.7 15.0": ["maida"], "14.1 3.4 11.9": ["buoyantly"], "-1.6 -2.4 14.8": ["ada"], "-0.8 19.9 18.8": ["bipod"], "5.1 -0.4 12.3": ["sil"], "6.1 6.7 25.3": ["thatching"], "2.8 10.2 6.1": ["starcast"], "3.4 38.3 3.8": ["counterforce"], "-0.7 2.2 15.1": ["juvie"], "9.4 -0.4 9.4": ["enthusiam"], "5.5 8.0 10.3": ["equitised"], "4.8 20.0 5.4": ["prohibitionists"], "3.0 3.7 9.3": ["nya"], "-6.9 -0.3 16.7": ["minerally"], "9.8 9.5 13.2": ["dimensioning"], "5.5 4.8 10.7": ["sodded"], "1.7 13.7 5.1": ["chadors"], "7.8 14.2 23.1": ["redden"], "14.7 5.7 7.8": ["rainswept"], "-2.1 7.3 4.6": ["ectopic"], "21.4 2.4 8.1": ["burbles"], "13.8 12.5 16.9": ["kevlar"], "13.3 16.5 8.4": ["grinches"], "0.5 17.7 -0.5": ["avowal"], "-6.7 6.3 8.1": ["bremelanotide"], "0.7 0.7 11.0": ["milliners", "pring"], "-10.0 2.0 0.1": ["replat"], "-0.1 21.4 6.7": ["governable"], "-1.1 6.9 -1.5": ["sexualizing"], "-9.9 4.9 5.0": ["tonsillectomies"], "2.3 6.0 14.3": ["talagang"], "7.1 13.1 6.7": ["thinktanks"], "-0.3 4.1 16.1": ["lumpectomies"], "3.9 7.4 3.8": ["rumbustious"], "6.4 6.8 10.9": ["communites", "koff"], "26.8 13.7 8.8": ["anthropomorphized"], "3.9 -3.9 2.4": ["novembre"], "7.2 7.3 19.0": ["elongates"], "8.5 7.4 7.8": ["subindices"], "14.8 7.3 -0.9": ["waterboy"], "9.7 8.2 15.2": ["roughened"], "4.6 17.1 13.8": ["spinelessness"], "2.5 2.2 17.8": ["tatting"], "13.8 10.3 9.9": ["dimensioned"], "-3.7 8.5 5.9": ["cholinergic"], "16.7 -1.3 21.9": ["opalescent"], "-2.6 7.6 6.0": ["ahd"], "11.5 -6.3 8.3": ["tx"], "11.8 13.1 11.9": ["shotstopper"], "7.5 18.1 20.9": ["phylum"], "2.7 6.9 9.1": ["hurrahs"], "6.0 10.2 15.4": ["palest"], "9.3 19.1 13.4": ["dingbat"], "9.7 8.3 2.9": ["bigging"], "2.3 10.4 4.7": ["sketchpad"], "0.4 8.8 3.1": ["basilicas"], "0.3 17.4 3.7": ["prophetess"], "5.5 3.1 10.4": ["wmv"], "16.5 1.6 11.3": ["hessian"], "13.5 18.4 2.3": ["wishfully"], "-2.8 11.4 12.9": ["dewater"], "6.5 9.7 5.2": ["finesses"], "3.2 12.5 12.4": ["stilling"], "0.9 29.5 5.6": ["soviets"], "2.8 0.8 -0.8": ["photobook"], "8.8 12.9 17.1": ["nothern"], "4.9 -0.7 -2.5": ["addtion"], "3.6 16.8 9.7": ["tendancy"], "-4.1 6.9 -2.3": ["rdquo"], "-2.4 23.5 3.2": ["multilateralist"], "11.7 13.2 6.9": ["neurotically"], "13.2 6.8 -0.8": ["gesticulated"], "4.2 8.8 11.0": ["jetport"], "8.9 28.7 10.9": ["incalculably"], "-0.3 26.6 -0.5": ["tribalist"], "-1.9 12.5 8.7": ["downdip"], "13.7 3.7 30.6": ["saltines"], "-6.1 4.0 3.4": ["downlinked"], "10.8 -1.6 7.7": ["moh"], "3.0 3.5 8.3": ["upcycling"], "7.4 21.1 9.4": ["youself"], "4.2 9.7 9.9": ["dre"], "3.1 14.3 13.3": ["offsuit"], "18.5 9.3 14.0": ["doozie"], "-0.4 0.8 1.5": ["tonsilitis"], "-0.8 8.9 -5.2": ["adviced"], "4.3 4.3 15.7": ["aniseed"], "6.2 2.8 5.3": ["swigged"], "-2.0 11.4 12.9": ["deadball"], "0.2 8.4 6.0": ["fugues"], "-0.6 4.4 26.4": ["sawlogs"], "10.0 3.0 1.4": ["distributers"], "7.1 14.5 5.0": ["surreality"], "1.6 4.7 2.6": ["bromate"], "8.8 12.1 7.7": ["parabolas"], "15.0 14.4 9.0": ["pussycats"], "6.1 10.9 27.7": ["cocklers"], "6.5 6.8 6.5": ["phenominal"], "5.1 4.0 16.9": ["casita"], "13.8 13.8 11.3": ["morosely"], "0.5 4.5 35.0": ["congee"], "4.0 4.7 -1.3": ["misdoings"], "1.3 13.2 5.8": ["deviancy"], "11.7 7.8 8.9": ["burnishers"], "4.1 10.2 15.7": ["zilla"], "0.4 -2.3 16.0": ["hing"], "-11.5 -1.0 -0.1": ["qualifed"], "-1.4 8.4 7.9": ["powerband"], "11.7 -0.6 13.1": ["noo"], "15.7 11.0 8.8": ["rotatable"], "15.5 8.4 24.8": ["bonbon"], "3.2 9.4 6.7": ["gop"], "1.0 -5.0 2.9": ["boardmember"], "9.5 6.2 4.5": ["pealed"], "-1.8 6.3 4.6": ["altos"], "9.0 14.9 0.8": ["fulminate"], "27.8 -0.6 8.3": ["industy"], "7.4 11.2 6.2": ["outjumping"], "9.2 7.4 8.6": ["penurious"], "5.2 3.3 7.4": ["advergaming"], "9.0 18.5 7.4": ["materialists"], "-10.6 17.0 16.4": ["portages"], "1.0 6.3 3.1": ["maureen"], "3.7 11.2 4.0": ["oneof"], "7.5 23.6 9.5": ["absolutists"], "-7.6 10.1 1.2": ["redesignate"], "-4.8 6.2 16.8": ["aman"], "10.1 4.8 -0.6": ["multiline"], "14.7 22.4 8.2": ["puppetmaster"], "-7.1 3.9 3.4": ["accountings"], "10.7 2.1 7.9": ["chubbier"], "-0.6 9.0 -1.5": ["grassfires"], "16.6 13.6 -0.3": ["vaporised"], "-0.9 15.8 17.9": ["gybes"], "4.6 15.1 11.5": ["cerebrum"], "-0.2 7.9 3.3": ["opensource"], "2.1 7.3 25.9": ["crunchiness"], "-5.3 5.2 23.6": ["cowpeas"], "6.4 8.6 14.7": ["hourslong"], "4.9 13.5 5.0": ["blurrier"], "5.4 12.3 16.0": ["squally"], "6.8 1.1 7.9": ["leisurewear"], "5.1 6.0 -6.9": ["transcriber"], "10.4 6.7 10.2": ["diadem"], "8.2 2.3 14.0": ["jojoba"], "4.8 18.3 10.2": ["impelling"], "4.2 7.2 7.4": ["flexicurity"], "11.3 15.5 17.6": ["deflectors"], "-1.9 6.7 1.8": ["confocal"], "6.8 14.4 30.1": ["northeaster"], "-2.1 9.2 5.2": ["interrelation"], "0.3 15.4 11.0": ["peremptorily"], "-3.8 -3.8 6.9": ["paraeducator"], "-1.0 8.6 7.1": ["whatsover"], "-7.7 3.4 0.9": ["privity"], "8.8 5.4 4.6": ["bifurcating"], "4.1 3.5 13.7": ["plasterwork"], "0.1 9.7 8.9": ["sequesters"], "0.3 12.1 4.3": ["interst"], "-2.7 6.4 2.0": ["overpromise"], "2.4 7.1 3.5": ["beeen"], "17.5 7.3 14.7": ["lolled"], "18.9 12.0 11.5": ["enfolded"], "4.3 9.1 4.5": ["unthreatened"], "10.1 19.4 18.3": ["warcraft"], "9.9 4.0 3.3": ["buidling"], "0.7 24.8 8.0": ["foreordained"], "2.2 8.7 7.1": ["byeline"], "-10.0 3.6 13.3": ["voicings"], "5.2 7.0 15.6": ["jong"], "0.4 31.5 8.2": ["rejectionism"], "2.7 0.2 11.1": ["implieds"], "-3.2 11.4 8.9": ["imetelstat"], "-11.7 14.0 10.4": ["liberos"], "2.3 0.4 24.7": ["breakbulk"], "-2.3 -0.1 2.1": ["hypospadias"], "7.8 5.6 8.8": ["ticketmaster"], "-5.4 9.8 7.7": ["recanvass"], "-2.1 4.7 14.2": ["pala"], "-9.5 8.6 8.0": ["oxygenates"], "-2.3 4.4 1.3": ["calibrators"], "1.8 -1.3 -0.9": ["kilotonnes"], "-0.4 14.2 10.1": ["lithological"], "12.5 7.8 28.7": ["aquaria"], "8.8 -3.4 5.1": ["signficantly"], "-6.8 4.4 17.3": ["triticale"], "11.0 4.9 12.9": ["honky"], "3.4 6.4 1.4": ["ampere"], "5.7 14.8 7.1": ["backrowers"], "10.7 7.6 5.8": ["competitiors"], "-3.5 12.2 8.2": ["nondeductible"], "2.9 8.1 10.3": ["wastages"], "1.5 6.8 11.7": ["blading"], "-3.8 5.7 5.5": ["thereabout"], "12.7 12.7 7.5": ["virals"], "-5.3 5.8 11.6": ["conjunctiva"], "9.6 3.4 25.5": ["bleu"], "7.1 6.6 6.5": ["sartorially"], "0.1 -2.4 14.9": ["lambskin"], "2.5 12.7 7.1": ["audibled"], "8.1 1.9 14.1": ["scotland"], "3.0 14.4 2.7": ["freinds"], "-3.7 -0.1 9.9": ["coverlets"], "-5.1 1.9 3.8": ["darunavir"], "2.2 15.9 13.4": ["idiosyncracies"], "3.4 8.3 9.9": ["nats"], "-3.7 -2.8 1.0": ["tb"], "0.4 -1.2 2.8": ["satisified"], "2.4 18.7 32.7": ["damselflies"], "3.3 20.7 6.6": ["feinting"], "15.2 13.6 20.1": ["doornail"], "13.5 10.5 5.2": ["crappiest"], "3.4 6.6 17.0": ["backsplashes"], "9.9 10.8 -2.0": ["democratizes"], "-1.5 -3.6 2.2": ["amortizes"], "0.5 14.0 21.5": ["brooder"], "2.8 -1.5 4.5": ["clark"], "6.9 -3.1 8.9": ["formfitting"], "-4.5 -6.8 4.9": ["unscored"], "5.7 7.7 4.3": ["unflashy"], "3.1 11.5 14.2": ["swissy"], "2.4 5.4 26.0": ["boatbuilders"], "-2.0 4.1 12.8": ["playgoers"], "9.5 6.7 8.6": ["hankers"], "-6.7 7.8 4.0": ["woreda"], "6.5 6.6 6.0": ["hv"], "0.9 8.5 4.4": ["linagliptin"], "11.3 0.3 25.2": ["paddleboats"], "4.7 5.9 1.0": ["supersymmetry"], "-1.0 20.0 5.4": ["seculars"], "-7.9 -5.1 5.2": ["estheticians"], "-3.3 -3.5 8.2": ["hippotherapy"], "6.2 18.2 -1.5": ["antechamber"], "14.9 0.9 5.8": ["wannabee"], "-0.5 6.1 6.8": ["archdeacon"], "19.1 12.8 8.8": ["fundament", "whizbang", "preseve"], "8.0 -0.2 -0.8": ["plusher"], "8.9 4.5 0.9": ["plantiffs"], "1.4 9.3 13.3": ["shaadi"], "4.4 9.8 16.4": ["harrow"], "-1.9 8.4 7.2": ["arr"], "9.5 8.2 6.8": ["diverter"], "3.2 -3.8 14.0": ["palanggas"], "0.3 19.2 4.5": ["feudalistic"], "-3.0 14.5 1.5": ["situtation"], "23.8 7.4 9.6": ["lassos"], "10.1 3.0 10.4": ["macbook"], "7.1 4.8 -0.0": ["nonflammable"], "6.6 1.8 13.6": ["kon"], "3.1 19.1 17.9": ["boll"], "-2.5 4.8 9.1": ["metoprolol"], "0.1 12.9 14.3": ["cj"], "3.3 0.0 4.0": ["pdfs"], "2.6 0.3 9.0": ["churchwide"], "10.9 14.5 25.6": ["psyllids"], "21.3 8.7 2.3": ["plughole"], "22.5 3.8 -10.3": ["headquaters"], "-5.4 1.0 7.4": ["feedyards"], "-2.2 4.3 7.8": ["etoposide"], "-2.6 11.2 8.9": ["defragmenter"], "2.7 14.7 10.0": ["pities"], "8.7 18.0 6.3": ["shouters"], "2.0 7.1 4.6": ["colonoscope"], "0.7 7.1 -0.6": ["prewritten"], "1.0 13.7 2.7": ["allurement"], "22.7 16.1 10.2": ["scaremongers"], "11.9 4.1 6.9": ["biro"], "-2.2 6.6 3.9": ["proofreaders"], "16.0 15.3 13.2": ["ghoulishly"], "-1.8 8.5 2.1": ["applauses"], "-5.8 5.0 14.6": ["gallerists"], "6.1 4.8 14.2": ["colorization"], "-1.0 16.5 14.3": ["beanballs"], "5.9 22.1 16.6": ["imbecility"], "14.5 6.1 8.5": ["piker"], "9.3 8.3 15.1": ["plonker"], "19.2 9.7 11.6": ["candymaker"], "3.9 14.3 14.5": ["kil"], "4.2 10.0 32.8": ["puri"], "10.6 6.1 -4.8": ["compatability"], "-1.1 4.9 12.4": ["epitaxy"], "-5.4 6.0 4.0": ["deteriorations"], "3.4 9.6 7.2": ["wenger"], "-0.6 3.1 15.8": ["freesia"], "7.3 10.6 12.1": ["tightwads"], "-2.7 -2.4 13.1": ["postprandial"], "-2.2 18.9 5.9": ["recharacterization"], "10.3 9.4 10.7": ["nerdish"], "1.5 5.2 2.7": ["santoor"], "-8.4 15.0 0.1": ["lustration"], "2.9 6.3 12.3": ["sara"], "2.2 7.6 -0.4": ["vitiating"], "11.5 6.6 9.9": ["govenrment"], "11.7 5.2 17.4": ["coagulated"], "-0.6 22.3 10.4": ["dualities"], "-3.6 6.3 3.7": ["sophs"], "3.6 11.5 3.8": ["earplug"], "3.9 0.1 6.7": ["micromachining"], "-4.1 12.3 28.2": ["tailwaters"], "3.0 7.8 6.0": ["phonons"], "2.9 9.1 7.6": ["pesters"], "7.1 4.1 15.2": ["maltodextrin"], "10.5 7.0 6.9": ["anisotropic"], "-7.1 13.4 5.2": ["dissimilarity"], "5.1 -1.9 17.7": ["tubulars"], "-1.0 15.0 7.9": ["comraderie"], "3.1 4.1 -0.0": ["ost"], "-2.0 0.3 8.3": ["bossa"], "5.9 -1.8 9.6": ["valances"], "-3.8 15.1 6.9": ["beggary"], "5.3 1.9 12.5": ["lunchbreak"], "7.1 9.7 21.3": ["muds"], "4.2 5.8 -0.3": ["encomium"], "-11.5 7.2 3.6": ["immunosuppressed"], "-1.5 2.6 11.4": ["sel"], "5.6 2.0 6.7": ["cruelled"], "3.3 11.1 6.2": ["urbanize"], "16.4 15.8 9.4": ["guillotines"], "0.3 6.7 3.0": ["archpriest"], "11.3 0.9 8.3": ["runing"], "3.8 8.6 9.4": ["naptha"], "5.3 19.0 8.5": ["lurkers"], "3.4 19.0 12.8": ["bridezilla"], "-8.6 0.3 0.6": ["averments"], "1.0 13.1 5.2": ["declaim"], "26.1 19.6 24.6": ["ladybird"], "4.1 6.9 6.8": ["sols"], "10.6 7.9 13.9": ["biopiracy"], "2.9 10.4 10.9": ["phenolics"], "9.3 5.4 11.7": ["stickups"], "-1.5 4.8 6.4": ["medicaments"], "7.1 9.2 11.5": ["crucifixions"], "-9.0 2.9 9.5": ["reoffering"], "5.6 0.2 7.5": ["tors"], "2.4 5.1 11.0": ["hydroxyapatite"], "-3.1 5.4 3.4": ["phlebotomists"], "4.1 2.7 1.9": ["arrondissement"], "0.6 1.0 11.9": ["deca"], "1.0 7.4 5.7": ["lopsidedness"], "-1.3 20.6 9.1": ["scenerio"], "-7.8 6.2 7.6": ["ambulation"], "3.2 0.4 10.7": ["outduelled"], "-7.0 7.2 -2.7": ["deputing"], "21.7 9.0 18.3": ["footmen"], "14.0 23.1 3.6": ["neutralises"], "-0.8 10.8 2.3": ["dramatises"], "4.3 -0.0 15.2": ["carotene"], "0.6 10.9 6.0": ["prision"], "4.8 10.6 3.1": ["entreating"], "-0.2 5.0 10.5": ["ponderings"], "1.4 12.8 5.5": ["irrelevancies"], "16.3 -3.3 5.6": ["equivilent"], "-8.7 10.7 3.5": ["thir"], "-6.6 3.0 22.6": ["kupuna"], "-0.5 10.0 1.6": ["occurences"], "-0.0 -0.4 10.6": ["yearolds"], "9.3 -3.5 7.9": ["oleochemicals"], "-0.3 5.7 12.3": ["interleaving"], "1.4 9.3 5.3": ["extempore"], "11.1 6.1 11.5": ["facies"], "6.2 4.5 26.7": ["larkspur"], "-7.8 5.2 2.1": ["antihypertensives"], "3.1 5.8 13.1": ["miscount"], "6.2 8.6 1.4": ["supportively"], "8.8 17.1 11.8": ["newshounds"], "1.1 6.0 1.2": ["forths"], "9.3 16.0 7.7": ["undefinable"], "5.7 0.4 8.2": ["yul"], "-2.9 6.1 11.4": ["yaoi"], "4.2 24.2 11.5": ["stealthier"], "5.7 1.1 6.5": ["swankier"], "7.8 2.3 6.1": ["regrade"], "-0.3 18.9 12.4": ["tapout"], "4.9 7.5 19.9": ["spiciest"], "3.9 8.6 9.9": ["lachrymose"], "-4.3 3.9 3.1": ["tetrachlorethylene"], "7.7 6.3 7.1": ["beter"], "7.5 8.1 13.0": ["phi"], "-5.5 -1.5 3.2": ["teriparatide"], "10.4 12.4 6.1": ["yapped"], "-1.1 2.8 1.4": ["videographed"], "2.5 14.7 5.5": ["allures"], "2.3 7.6 -2.4": ["becaue"], "8.7 42.5 6.7": ["missles"], "10.7 11.1 10.2": ["agrofuels"], "7.5 10.5 12.1": ["transgenics"], "-3.0 -0.1 7.2": ["reinjected"], "14.8 12.3 14.5": ["phantasmagoria"], "3.2 19.8 4.9": ["lurker"], "2.9 8.8 5.1": ["aeromagnetic"], "-5.1 8.0 6.6": ["bandmaster"], "12.8 -0.1 9.6": ["quids"], "7.3 12.7 1.7": ["cia"], "9.4 12.0 16.6": ["clearcuts"], "9.1 0.2 7.0": ["iowa"], "5.5 22.8 11.8": ["dirtbags"], "3.2 4.8 0.4": ["radioimmunotherapy"], "9.5 8.9 39.8": ["parrotfish"], "-10.6 2.1 -1.7": ["annexures"], "4.8 9.4 9.1": ["aerobridges"], "9.8 12.8 7.8": ["eveyone"], "1.7 21.7 12.8": ["sanguinary"], "12.8 14.2 12.5": ["furled"], "1.0 5.2 11.4": ["microcaps"], "10.9 -4.0 2.3": ["uit"], "-6.0 8.3 4.3": ["antimalarials"], "8.9 8.3 36.9": ["frisee"], "-11.3 -2.4 19.5": ["weaners"], "8.3 9.8 6.5": ["striver"], "2.3 3.7 2.6": ["quaternary"], "6.0 9.1 -3.3": ["tesla"], "16.0 8.6 19.0": ["befouled"], "6.5 1.6 13.8": ["jewellry"], "5.6 17.5 14.8": ["transects"], "0.4 7.5 15.2": ["agrarians"], "7.1 9.0 34.4": ["yakitori"], "7.6 22.7 7.0": ["monomaniacal"], "9.6 -0.7 14.2": ["soled"], "10.9 8.4 2.1": ["satirising"], "5.6 6.3 6.6": ["churchyards"], "-2.9 18.9 5.8": ["unpatrolled"], "6.3 8.4 6.2": ["mappers"], "6.3 12.2 13.7": ["hybridize"], "13.0 23.4 6.8": ["cordite"], "10.7 10.9 9.0": ["supergroups"], "7.6 4.1 8.3": ["pgm"], "-5.2 14.3 5.7": ["preconditioned"], "-3.3 0.6 1.4": ["competative"], "4.0 -0.5 4.5": ["unilingual"], "-0.8 5.0 14.2": ["littermates"], "-2.2 5.6 6.3": ["segmentations"], "6.9 13.8 25.5": ["flycatchers"], "5.8 8.1 1.3": ["bussiness"], "9.8 9.9 15.0": ["oot"], "21.4 1.0 20.3": ["potbellied"], "9.0 10.8 12.3": ["etymological"], "0.5 9.5 5.4": ["neccessarily"], "6.9 5.4 12.7": ["shuffler"], "2.2 8.5 27.3": ["juncos"], "-1.2 10.4 5.0": ["teleworker"], "4.0 4.2 3.1": ["hotshoe"], "8.9 14.7 0.6": ["nonsensically"], "0.1 5.9 6.3": ["aliments", "ghts"], "3.5 5.0 29.4": ["springer"], "-0.2 6.4 11.1": ["namespaces"], "-4.0 11.0 6.0": ["goaling"], "11.9 25.8 2.9": ["ineluctably"], "11.1 8.7 23.7": ["lobelia"], "0.1 9.5 12.2": ["hafta"], "-3.4 9.4 1.9": ["activeness"], "2.9 5.6 0.2": ["classifiers"], "-0.8 6.0 28.5": ["oolong"], "4.0 14.1 5.8": ["disquisition"], "-7.2 9.2 13.9": ["denitrification"], "-3.5 9.1 6.9": ["rootlessness"], "-0.1 11.8 5.4": ["nondivisional"], "10.7 12.7 3.9": ["distractedly"], "-5.9 3.2 5.7": ["senates"], "13.5 10.7 14.5": ["breakbeats"], "5.2 8.8 2.1": ["postpress"], "12.0 16.2 11.0": ["crapola"], "-7.7 1.8 9.0": ["viticulturist"], "6.2 9.2 8.8": ["quavering"], "6.8 19.9 2.4": ["bads"], "9.7 5.1 16.1": ["crinkles"], "7.2 -4.8 9.9": ["copyrighting"], "-4.3 10.2 11.7": ["proroguing"], "11.4 12.0 15.2": ["carmine"], "2.6 17.2 2.4": ["factotum"], "-8.3 2.0 -2.7": ["subscales"], "-4.9 7.1 5.1": ["adenocarcinomas"], "4.2 19.8 1.7": ["simultaneity"], "-2.8 21.5 14.6": ["disproportionality"], "15.3 13.1 14.1": ["scabby"], "17.7 -1.2 4.7": ["moonwalked"], "5.1 4.3 9.5": ["railroaders"], "18.4 15.5 22.9": ["gullets"], "5.2 17.0 6.2": ["faintness"], "7.7 14.3 16.9": ["gaffers"], "3.6 -1.2 1.2": ["copyrightable"], "4.8 -3.9 4.7": ["dm"], "-2.6 12.2 20.4": ["jiujitsu"], "17.0 11.6 42.5": ["mollusc"], "13.8 15.7 10.9": ["splutters"], "8.5 -0.1 16.5": ["wales"], "8.7 12.1 -0.5": ["dissembled"], "5.8 14.8 4.2": ["geotagged"], "12.2 -1.2 14.8": ["olestra"], "8.5 10.1 15.1": ["regrown"], "22.7 12.7 2.4": ["fledgeling"], "13.1 4.6 21.2": ["silvered"], "5.9 4.9 0.9": ["einer"], "13.6 10.0 1.9": ["informatization"], "5.9 11.9 16.7": ["mudstone"], "8.8 0.1 16.4": ["virginia"], "8.9 24.0 15.8": ["faerie"], "10.3 15.1 6.0": ["clubgoer"], "4.2 6.1 11.1": ["pressers"], "-5.2 36.0 -2.4": ["assassinates"], "-3.7 14.9 2.0": ["scalds"], "-1.0 9.4 8.5": ["unconsummated"], "6.9 15.1 13.3": ["animism"], "4.2 -1.5 11.9": ["moore"], "-1.5 1.5 2.9": ["skydives"], "-7.7 16.6 -1.2": ["interrogatory"], "11.5 15.1 5.3": ["despondently"], "-4.2 9.5 7.1": ["cedants"], "-1.7 8.9 3.1": ["waqf"], "6.0 8.7 3.7": ["counterdemonstrators"], "-10.9 -6.6 -1.2": ["appearences"], "2.9 4.7 10.8": ["doublet"], "11.1 2.6 13.0": ["daggy"], "-4.3 20.2 7.6": ["almsgiving"], "5.9 21.9 15.6": ["gybing"], "-2.9 10.5 4.8": ["moiety"], "8.8 3.7 18.7": ["leks"], "-1.9 18.2 6.7": ["intuited"], "5.2 11.5 11.9": ["orchestrators"], "17.0 -6.1 -1.9": ["highprofile"], "12.9 2.0 7.9": ["heathcare"], "9.0 12.8 17.1": ["switchblades"], "-2.7 9.6 -7.8": ["comitted"], "9.6 6.2 1.7": ["polycarbonates"], "5.1 7.2 22.4": ["chapati"], "1.0 10.2 9.9": ["epicatechin"], "1.5 17.0 10.8": ["bullshitting"], "11.4 13.3 41.7": ["petrels"], "10.1 17.5 17.3": ["shoulderblock"], "-6.3 3.3 4.4": ["continuo"], "3.5 3.6 7.8": ["cushier"], "3.0 5.1 12.5": ["tini"], "-5.0 7.6 8.5": ["clarithromycin"], "15.1 9.1 13.1": ["ooooh"], "0.4 23.5 1.5": ["interpose"], "2.9 5.1 17.4": ["vermicomposting"], "-2.1 1.8 1.7": ["clarinettist"], "4.0 4.4 7.1": ["overeducated"], "4.8 22.0 17.1": ["magick"], "4.0 -1.0 7.2": ["locos"], "1.9 6.3 18.4": ["debarked"], "19.5 9.4 19.5": ["pendulous"], "8.9 11.6 2.2": ["aiport"], "9.2 16.3 15.6": ["snowfield"], "5.5 7.8 7.6": ["sanely"], "8.8 12.0 41.6": ["grunion"], "7.4 4.2 6.8": ["televsion"], "7.8 -2.7 8.9": ["vj"], "7.7 3.4 4.9": ["dummying"], "-6.8 4.4 6.2": ["risedronate"], "-12.8 8.1 11.3": ["gup"], "5.8 0.9 5.9": ["unsubsidised"], "9.5 10.7 2.5": ["desparately"], "10.5 20.8 8.3": ["terrorises"], "18.4 9.7 26.1": ["puffball"], "-4.8 16.7 3.9": ["nonstarters"], "-10.3 11.9 4.4": ["telecommunicators"], "-6.1 5.1 1.3": ["shuls"], "-3.4 15.2 11.9": ["outvote"], "7.7 2.3 13.3": ["nei"], "6.4 9.4 4.6": ["reabsorb"], "17.4 3.2 9.2": ["mew"], "4.2 12.1 3.7": ["transportability"], "-1.6 0.6 10.1": ["sma"], "-5.8 5.7 9.8": ["vincristine"], "-0.4 9.3 3.2": ["frostiness"], "-3.1 -0.6 -2.0": ["quitted"], "7.1 6.1 -2.9": ["connectable"], "14.9 10.1 22.2": ["worktable"], "8.0 4.9 9.4": ["outparcel"], "8.3 8.0 18.7": ["preppies"], "0.8 6.7 4.0": ["metabolise"], "-4.8 11.8 8.0": ["contracture"], "-2.5 9.9 12.4": ["unsystematic"], "4.4 2.4 23.0": ["gesso"], "-7.3 8.0 0.9": ["doorknocking"], "14.5 12.2 15.2": ["grumps"], "2.3 16.4 3.5": ["aerostats"], "5.9 24.1 2.8": ["secessionism"], "-5.1 13.6 12.2": ["garnishments"], "-7.3 3.9 2.8": ["hydrogeological"], "-14.0 23.3 -1.3": ["doctrinally"], "-10.7 16.8 4.7": ["winnability"], "-1.2 5.6 7.4": ["peritoneum"], "8.0 5.0 7.1": ["sulphates"], "5.4 6.8 27.1": ["horchata"], "-2.3 10.9 5.0": ["deprecate"], "1.7 -6.8 2.8": ["precocity"], "0.3 8.0 5.1": ["submicron"], "12.1 8.7 5.6": ["overlayed"], "7.1 2.1 11.2": ["bae"], "21.7 24.9 26.9": ["housefly"], "6.4 9.2 21.4": ["teakwood"], "7.5 18.3 6.1": ["flashbulb"], "-4.3 0.3 28.4": ["sheepmeat"], "-4.1 14.0 9.4": ["toolpaths"], "-0.3 6.5 6.9": ["monoclonal"], "4.0 23.5 9.2": ["bushwhacked"], "4.3 1.2 -1.4": ["conv"], "-6.0 8.5 2.5": ["demodulators"], "9.9 19.6 15.2": ["pasttime"], "-2.7 4.7 4.3": ["parameterized"], "3.6 3.2 13.5": ["nae"], "-1.5 9.3 11.2": ["floodings"], "-0.2 11.0 8.3": ["pronation"], "2.1 8.1 12.8": ["politicial"], "-3.0 5.7 11.7": ["appendectomies"], "10.6 1.0 29.8": ["bannock"], "-3.5 17.1 8.4": ["proneness"], "3.5 -1.3 9.6": ["picograms"], "1.0 8.8 1.0": ["unshared"], "3.7 3.7 15.8": ["woodcarvers"], "-0.4 16.9 0.4": ["underrating"], "23.0 9.2 7.5": ["uncoiled"], "-0.2 6.6 9.1": ["craniotomy"], "14.3 1.9 -2.3": ["whic"], "4.0 -1.9 4.1": ["kunas"], "-9.4 -1.3 2.9": ["cowritten"], "-1.3 1.2 12.4": ["sportscasts"], "-0.9 8.5 3.9": ["zx"], "20.2 11.6 29.0": ["warty"], "18.8 19.8 17.2": ["electromagnet"], "11.7 9.7 35.0": ["floe"], "-1.5 15.6 13.2": ["obliques"], "5.9 3.3 17.2": ["palomino"], "3.0 7.0 12.4": ["skiiers"], "0.8 6.1 13.6": ["clement"], "-7.7 14.1 4.3": ["discords"], "18.8 14.7 16.1": ["sequoia"], "6.9 5.5 -1.8": ["nanofiber"], "3.6 6.9 21.4": ["crabbed"], "-0.6 1.2 5.1": ["debarring"], "16.0 20.9 7.3": ["impotently"], "-5.8 5.0 5.9": ["telecine"], "11.1 19.3 13.3": ["cluelessly"], "0.5 8.2 9.6": ["draftsmanship"], "10.0 6.0 11.2": ["vic"], "15.4 11.3 21.2": ["excretes"], "0.7 11.1 10.7": ["sixers"], "4.3 6.6 17.1": ["sierra"], "7.0 12.0 8.3": ["manipulatives"], "-6.9 11.3 5.9": ["clearness"], "18.9 4.1 8.1": ["autoparts"], "-1.7 7.9 1.1": ["cytosine"], "9.6 7.8 8.1": ["hogan"], "16.0 5.3 14.2": ["outers"], "0.6 -2.3 10.7": ["maging"], "25.3 10.1 8.0": ["plonking"], "-5.4 16.9 -3.5": ["unpreventable"], "15.0 6.2 29.8": ["griddles"], "4.0 7.6 15.8": ["nightshirt"], "-7.9 7.6 -1.4": ["embolic"], "6.5 -2.4 -4.8": ["adminstrator"], "5.7 -1.5 37.9": ["deboned"], "-4.3 19.6 7.7": ["songun"], "6.8 -0.8 3.2": ["unsubstantial"], "9.8 19.0 3.8": ["suppressant"], "-6.8 11.7 2.4": ["commonalties"], "22.7 1.2 9.3": ["gazers"], "0.5 1.8 -2.5": ["glamorised"], "5.7 9.4 6.4": ["disinvesting"], "17.9 11.6 21.7": ["whatevers"], "-1.4 5.1 8.5": ["sarangi"], "7.5 19.9 15.8": ["crookedness"], "1.9 11.2 6.0": ["sidenetting"], "-13.7 6.7 10.1": ["hiatuses"], "-0.3 7.0 9.2": ["pipetting"], "8.0 0.7 10.1": ["carbonfibre"], "4.5 13.0 8.4": ["hootin"], "-1.0 18.4 6.1": ["passiveness"], "1.8 11.5 14.2": ["kickboxers"], "5.5 15.4 8.5": ["unfriended"], "18.1 11.7 5.9": ["sepulchral"], "8.6 4.6 12.7": ["baronial"], "-4.3 4.1 0.1": ["bupivacaine"], "3.7 15.5 4.3": ["wreckless"], "-3.3 10.9 17.5": ["unbuildable"], "3.7 16.8 0.4": ["propagators"], "7.1 6.3 5.7": ["farcically"], "12.8 11.1 16.2": ["wally"], "-1.9 11.8 7.1": ["denouncements"], "-0.7 6.5 10.7": ["lysis"], "-5.3 8.3 10.8": ["nucleoside"], "12.6 14.1 2.7": ["powerfull"], "3.8 16.9 13.1": ["xenical"], "11.0 7.5 5.5": ["centerfolds"], "5.1 -2.7 -4.7": ["zanox"], "15.8 25.9 10.6": ["earthling"], "-4.9 0.1 6.9": ["refreshers"], "7.3 6.0 7.3": ["copacetic"], "1.6 14.8 6.6": ["romanticizes"], "0.5 13.8 8.9": ["peroration"], "-1.8 0.1 11.1": ["neonate"], "17.7 9.2 10.4": ["clocktower"], "8.1 15.4 -1.0": ["falsities"], "2.3 2.6 3.7": ["momentos"], "3.5 12.8 7.0": ["fiances"], "-3.2 11.9 4.2": ["rememberance"], "-2.8 9.7 13.9": ["citrulline"], "6.0 1.6 9.3": ["tna"], "-1.2 3.5 9.9": ["templated"], "-2.7 0.3 7.2": ["transloading"], "6.9 5.9 7.9": ["jj"], "3.8 5.2 16.1": ["sprinklings"], "14.0 10.4 3.3": ["craptastic"], "5.3 9.4 5.5": ["inducers"], "2.8 -1.8 6.3": ["austin"], "11.1 1.1 5.7": ["yammer"], "9.3 24.9 2.9": ["superheroine"], "6.9 6.9 12.7": ["cuneiform"], "4.9 4.6 39.8": ["smolt"], "9.2 1.3 8.9": ["weans"], "6.1 21.2 18.0": ["tribemates"], "5.1 21.5 7.9": ["meteoroids"], "23.7 5.2 31.2": ["blubbery"], "0.4 15.6 5.3": ["airsoft"], "0.4 3.8 1.4": ["blankings"], "6.2 13.3 11.1": ["tenderhearted"], "3.2 24.0 9.0": ["complacence"], "5.4 3.8 -0.1": ["reknown"], "5.0 3.5 11.4": ["jailbait"], "11.8 15.9 10.3": ["moustached"], "-1.3 7.6 7.5": ["aldehydes"], "-6.2 9.7 9.8": ["trixbox"], "-5.8 3.4 9.4": ["annealed"], "9.8 10.8 16.3": ["laddie"], "5.8 1.6 6.2": ["tkts"], "8.4 5.0 -4.5": ["brushless"], "2.4 3.5 9.1": ["revelries"], "3.8 10.5 5.1": ["isotropic"], "4.8 14.7 3.2": ["stenography"], "-3.0 11.5 9.1": ["repechages"], "1.6 14.0 -0.7": ["occultism"], "11.1 11.5 -7.9": ["shopkick"], "-1.7 5.9 6.2": ["superminis"], "1.7 4.7 12.7": ["digressive"], "8.1 5.7 6.4": ["microsphere"], "-3.4 2.8 10.1": ["breezier"], "6.7 3.8 14.2": ["steriods"], "4.9 14.8 11.4": ["delimit"], "6.0 10.9 6.0": ["thrusted"], "2.9 7.1 1.0": ["downburst"], "33.9 5.4 7.3": ["conglom"], "10.8 25.9 16.9": ["noobs"], "-5.4 7.6 4.1": ["severities"], "5.2 6.8 27.8": ["poblano"], "-4.0 12.7 5.0": ["nitromethane"], "9.6 0.8 10.0": ["freighting"], "-2.6 2.8 10.5": ["fingerpicking"], "-5.2 4.0 5.7": ["toastmaster"], "-0.7 7.2 4.9": ["splinted"], "4.2 22.3 5.9": ["strivings"], "-6.5 4.7 18.0": ["macronutrients"], "-0.2 -2.7 -0.6": ["enrols"], "4.2 19.5 15.3": ["dictums"], "1.4 1.9 11.3": ["tonner"], "-4.6 9.0 12.7": ["tetrahydrocannabinol"], "5.2 13.7 6.8": ["recombining"], "-1.3 3.3 1.5": ["fluorinated"], "1.9 4.8 2.3": ["coverted"], "12.0 8.1 0.9": ["wheedled"], "1.4 10.8 9.6": ["beatboxer"], "5.5 12.8 21.4": ["revetment"], "-2.7 1.7 6.3": ["adefovir"], "5.4 3.0 11.9": ["sg"], "11.6 6.3 16.3": ["manicuring"], "18.0 6.5 23.8": ["beachcomber"], "-4.5 9.0 9.4": ["understeering"], "21.1 12.2 8.9": ["gushers"], "-2.3 12.8 44.8": ["gillnets"], "13.6 15.9 7.9": ["financialization"], "3.2 2.8 9.2": ["capitalizations"], "8.4 8.3 11.8": ["taspoglutide"], "2.2 8.1 11.9": ["dma"], "12.5 14.3 14.0": ["cupidity"], "-4.1 12.2 5.7": ["governability"], "9.2 7.2 5.1": ["synthesising"], "-3.1 7.6 6.6": ["explaination"], "9.7 11.4 9.9": ["drabness"], "-3.5 0.2 21.0": ["wholemeal"], "1.7 1.2 6.8": ["straighteners"], "15.3 8.6 27.7": ["corndogs"], "6.1 -0.7 31.7": ["mesclun"], "-9.7 -4.5 -4.0": ["postholder"], "-3.7 -4.4 2.2": ["bifeprunox"], "3.4 9.3 8.8": ["supernodes"], "-1.4 11.4 4.2": ["tunesmiths"], "4.0 0.9 -0.5": ["brandable"], "17.2 21.4 16.9": ["pukes"], "5.1 3.3 14.5": ["lht"], "6.3 3.0 14.9": ["mehendi"], "-0.2 -2.6 2.5": ["touchup"], "9.3 1.1 7.6": ["ballpoint"], "18.9 -0.1 -2.4": ["advertisments"], "13.5 15.4 7.8": ["fief"], "1.3 -2.4 9.8": ["anganwadis"], "-8.5 0.2 13.7": ["spays"], "1.5 6.0 8.9": ["vaccinates"], "7.8 3.1 9.7": ["corraled"], "12.8 2.7 6.9": ["luvvies"], "1.2 11.6 7.2": ["venerates"], "-3.4 -0.3 -0.1": ["conformant"], "24.6 10.4 21.1": ["latticed"], "7.3 10.2 26.8": ["gondolier", "lemang"], "2.2 11.6 -4.4": ["blackballing"], "10.8 23.5 10.6": ["spirt"], "4.4 2.5 17.1": ["angora"], "-6.5 6.8 15.2": ["mutuel"], "-0.8 0.3 4.9": ["ors"], "-1.5 12.0 -1.6": ["nervewracking"], "-3.1 11.9 5.7": ["enuf"], "0.1 3.5 20.6": ["shu"], "12.5 22.4 15.4": ["baseliners"], "6.9 -0.6 16.4": ["slighly"], "5.3 20.2 1.6": ["distractive"], "7.5 -0.7 2.2": ["denver"], "4.7 29.4 2.3": ["brutalise"], "6.8 20.0 9.0": ["goondas"], "13.4 10.2 11.2": ["stompers"], "8.2 5.2 20.4": ["pendent"], "0.9 24.4 11.9": ["goyim"], "-3.7 19.3 8.9": ["lasing"], "18.7 23.6 11.3": ["manliest"], "11.7 11.4 14.4": ["throwin"], "8.0 14.9 21.0": ["sliotar"], "0.7 13.1 24.3": ["rosebushes"], "2.5 11.8 13.7": ["couloir"], "9.5 9.8 -0.2": ["visualizer"], "-1.4 1.4 11.6": ["culottes"], "8.3 3.1 20.3": ["queenly"], "12.3 10.2 14.8": ["hags"], "0.3 12.3 8.4": ["bullsh"], "8.9 0.0 12.3": ["jp"], "7.4 8.1 9.0": ["funs", "turny"], "14.7 15.2 6.4": ["perpendicularly"], "23.2 5.6 10.5": ["splashier"], "3.0 2.0 16.8": ["katie"], "-6.3 2.4 3.4": ["drospirenone"], "6.3 10.2 -3.5": ["dictaphone"], "1.0 21.5 16.8": ["biocontrol"], "9.2 11.6 11.6": ["bareheaded"], "11.5 13.0 8.3": ["yowl"], "-3.2 12.1 8.1": ["interfacial"], "3.4 28.0 20.3": ["scuds"], "1.5 2.8 8.8": ["palimony"], "13.7 22.9 13.7": ["nerf"], "-0.5 12.1 7.4": ["guiltier"], "-2.8 4.1 9.8": ["comediennes"], "-4.1 2.3 8.8": ["blacktopped"], "-1.8 2.7 6.0": ["jewelleries"], "0.4 15.4 -0.6": ["resourcefully"], "-6.5 6.9 11.2": ["refinancers"], "9.7 1.7 4.8": ["lui"], "10.5 18.8 5.9": ["opposers"], "19.8 1.5 5.0": ["besuited"], "15.8 10.6 16.3": ["featherbed"], "-1.8 -3.9 0.2": ["substudy"], "-5.9 8.1 16.9": ["farrowing"], "-0.1 4.8 1.6": ["recontest"], "-1.7 -0.5 3.7": ["hillier"], "-1.4 6.2 6.7": ["dimers"], "-2.6 0.3 -0.6": ["overprescribing"], "-0.7 6.3 9.0": ["sunsetting"], "6.9 1.7 7.1": ["elle"], "-3.9 15.3 17.4": ["squamous"], "7.8 14.2 21.4": ["sepulcher"], "2.8 9.9 17.1": ["mudding"], "9.2 13.4 14.5": ["areal"], "16.8 11.0 10.2": ["bleedin"], "-1.3 1.8 0.5": ["bickers"], "-7.5 7.4 -3.9": ["condoling"], "2.4 -0.5 11.7": ["itong"], "12.0 1.0 19.0": ["ironstone"], "13.1 11.9 9.4": ["spacial"], "-0.1 9.3 2.0": ["madarsa"], "-1.0 1.8 0.8": ["femtoseconds"], "7.0 10.1 0.1": ["landmen"], "9.1 14.2 30.4": ["seamount"], "-5.8 2.3 11.3": ["shigellosis"], "18.1 7.9 13.7": ["brazier"], "12.1 4.8 11.9": ["blowsy"], "13.0 7.7 14.8": ["daybeds"], "5.9 10.1 8.7": ["namaste"], "0.6 3.1 -3.5": ["reformulations"], "4.1 2.8 5.7": ["borates"], "14.1 9.7 6.0": ["priapic"], "10.3 8.7 13.1": ["amuck"], "4.8 22.9 6.9": ["manoeuvering"], "6.2 11.9 7.5": ["forestalls"], "-0.8 14.7 8.7": ["expiation"], "-2.2 3.9 6.9": ["pianism"], "13.8 12.1 5.7": ["pseudoscientific"], "0.6 -2.1 2.4": ["mls"], "-2.0 6.2 14.1": ["deburring"], "7.2 12.7 4.7": ["overachievement"], "10.5 4.1 17.9": ["aboot"], "3.3 8.4 12.7": ["splinting"], "-11.9 -0.1 6.8": ["dzongkhags"], "3.6 19.4 4.9": ["sustainer"], "-2.7 2.8 13.7": ["tola"], "4.4 13.3 8.3": ["interrelations"], "14.4 7.5 12.4": ["unstick"], "7.6 14.3 5.3": ["vapidity"], "0.9 6.7 8.0": ["symptomless"], "7.5 8.1 20.3": ["hydroplanes"], "-2.5 1.9 4.7": ["sugammadex"], "3.0 10.0 25.3": ["transoms"], "-7.4 2.4 21.3": ["raws"], "11.7 -0.4 14.1": ["dinero"], "-3.1 8.2 6.0": ["galactose"], "4.3 6.1 9.2": ["sql"], "10.9 4.2 12.9": ["afterbirth", "cornicing"], "-7.7 2.8 7.5": ["councilwomen"], "-2.4 12.6 4.9": ["overdriven"], "15.1 0.8 36.5": ["portobello"], "1.2 18.1 6.8": ["backdraft"], "-0.2 14.8 4.7": ["urgencies"], "-7.5 0.8 14.0": ["unallotments"], "-5.3 4.8 12.9": ["folksong"], "1.5 10.2 11.6": ["pleasers"], "10.7 5.8 10.2": ["tantalizes"], "8.3 6.1 3.6": ["baronet"], "-2.4 16.1 8.1": ["sternness"], "8.9 16.8 12.1": ["immobilizes"], "13.4 8.1 40.6": ["chargrilled"], "3.0 12.6 10.8": ["mutational"], "0.0 16.4 21.1": ["sealift"], "10.2 3.7 13.4": ["bevvy"], "4.6 15.1 -4.9": ["proselytizers"], "6.4 7.1 9.1": ["guyliner"], "6.9 11.9 5.2": ["spritzing"], "-3.7 -0.4 13.1": ["hyaluronan"], "1.5 1.4 12.0": ["fibro"], "10.7 20.2 22.6": ["moonrise"], "18.5 12.4 10.0": ["disconsolately"], "-4.7 4.0 6.9": ["ocurred"], "22.6 13.8 10.4": ["hackery"], "11.5 6.6 7.1": ["diddling"], "11.6 8.4 3.4": ["microbubbles"], "14.1 23.3 10.9": ["familiars"], "17.0 22.1 21.1": ["sunbeam"], "9.0 7.9 5.2": ["thegovernment"], "7.0 4.6 -2.5": ["turing"], "8.5 2.0 -0.5": ["phenyl"], "6.8 9.7 0.4": ["corrector"], "7.5 6.8 19.5": ["gastropubs"], "6.7 10.4 14.8": ["ridgetops"], "16.7 10.8 36.9": ["crouton"], "2.1 2.7 -10.1": ["relased"], "0.1 8.5 12.1": ["astrocyte"], "5.4 4.3 10.4": ["jitteriness"], "-6.3 13.6 1.4": ["enunciates"], "1.9 -1.7 -2.1": ["sonographer"], "1.9 0.0 11.3": ["resequencing"], "1.5 20.2 7.2": ["universals"], "2.9 5.9 34.7": ["springers"], "-2.6 19.9 -6.4": ["lionizing"], "-1.4 5.0 9.6": ["runouts"], "6.5 5.0 17.2": ["subprimes"], "7.3 10.8 5.6": ["inessential"], "13.2 13.6 14.6": ["taiga"], "12.8 3.0 -6.5": ["lauched"], "4.2 5.5 25.0": ["nacre"], "7.6 7.6 0.9": ["nerdiest"], "22.2 7.1 14.1": ["snaffling"], "-3.1 33.3 14.4": ["loadout"], "-1.8 8.1 2.3": ["midfoot"], "3.5 8.8 13.0": ["derailleur"], "1.7 9.0 14.5": ["uproariously"], "-0.5 4.4 22.6": ["frostings"], "5.7 -5.4 10.2": ["loh"], "16.8 19.6 6.4": ["bedfellow"], "-4.1 -1.0 12.5": ["leucine"], "8.9 13.0 4.1": ["storable"], "2.9 10.2 7.8": ["cassiterite"], "-13.5 7.3 -0.4": ["anticholinergic"], "15.9 17.1 1.2": ["resiliently"], "-3.9 2.9 -6.1": ["fulfiling"], "9.2 18.1 10.0": ["mockers"], "17.1 3.8 13.5": ["scantily"], "11.3 5.6 10.5": ["confected"], "12.0 -3.6 6.9": ["ig"], "-5.0 7.2 1.7": ["esomeprazole"], "2.3 9.1 16.6": ["mischievousness"], "-3.2 0.6 -1.5": ["convoke"], "-2.7 12.6 14.9": ["naa"], "3.6 15.5 6.5": ["squibs"], "4.2 -0.9 -0.0": ["greenroom"], "8.4 14.0 7.8": ["blimey"], "3.3 7.8 9.3": ["sudo"], "10.6 13.5 5.4": ["forefingers"], "0.5 11.9 8.6": ["knowingness"], "7.1 11.7 6.0": ["bushwalker"], "7.6 16.7 9.4": ["philosophize"], "-0.7 5.1 9.7": ["criminalists"], "14.4 8.9 -0.7": ["bangalore"], "4.8 18.2 12.0": ["earworm"], "-0.8 17.9 -2.6": ["tribalistic"], "6.3 16.2 3.7": ["leafletting"], "11.9 15.5 23.9": ["birdfeeder"], "11.5 3.8 33.7": ["julienned"], "1.5 5.0 26.9": ["lupins"], "5.5 10.9 14.0": ["downswings"], "4.7 15.5 8.6": ["obsequiousness"], "3.8 8.8 -0.5": ["waht"], "-1.8 16.9 15.4": ["poolies"], "0.8 2.2 15.4": ["grammy"], "-8.3 6.5 9.2": ["commissionable"], "-1.3 7.3 12.3": ["chippiness"], "5.8 11.9 7.1": ["uninvolving"], "15.6 22.5 3.8": ["disrupter"], "9.4 5.3 12.8": ["nuzzles"], "6.7 23.3 15.3": ["gaijin"], "17.3 6.1 -0.2": ["renationalisation"], "4.8 15.9 9.6": ["fornicate"], "1.9 -9.2 -0.9": ["prequalify"], "-2.1 10.1 8.2": ["randomisation"], "-7.7 -0.2 5.2": ["thermoset"], "24.6 14.3 14.2": ["gazillionaire"], "-5.5 5.3 -0.9": ["coachability"], "0.8 -2.4 0.9": ["sough"], "13.1 15.5 1.6": ["powderkeg"], "-2.3 0.4 -2.5": ["honouree"], "13.5 10.0 1.5": ["sux"], "3.9 5.9 13.3": ["mala"], "12.1 1.6 13.6": ["creamers"], "11.8 9.4 28.1": ["deers"], "9.0 27.9 18.3": ["symbiote"], "2.0 1.3 3.7": ["photogrammetric"], "4.7 8.4 5.2": ["vicriviroc"], "5.7 15.4 13.5": ["pixilation"], "18.0 17.8 7.8": ["punchbag"], "9.1 7.4 -0.2": ["reanimation"], "7.4 -4.0 15.8": ["soupcon"], "-0.0 4.3 7.4": ["unamplified"], "11.5 24.7 7.8": ["toilers"], "-1.6 9.4 4.0": ["syntheses"], "0.7 9.5 7.7": ["mujhe"], "8.0 5.1 11.5": ["luaus"], "-1.5 2.6 7.1": ["shirttails"], "6.0 10.0 6.8": ["factness"], "2.3 12.9 10.0": ["printf"], "2.3 7.7 -0.5": ["electrolyzer"], "-7.8 6.0 8.4": ["extenuating"], "8.3 -1.8 8.2": ["skateboarded"], "-7.9 3.7 4.8": ["emollients"], "21.9 4.7 11.6": ["rejigs"], "7.2 11.8 11.0": ["beatin"], "6.8 14.9 10.4": ["bureaucratese"], "6.6 2.1 22.1": ["pili"], "8.5 7.8 30.2": ["succulence"], "10.0 5.5 19.9": ["atlantic"], "10.5 11.5 2.9": ["humanised"], "-1.1 5.2 -3.4": ["avaiable"], "23.1 12.2 7.8": ["hugeness"], "-7.7 8.0 10.9": ["sulphites"], "7.1 14.8 -1.2": ["presidentially"], "3.5 19.4 5.9": ["yeomen"], "1.7 13.0 4.0": ["ghettoization"], "8.3 13.3 10.0": ["cypher"], "-11.9 13.9 9.5": ["fatals"], "11.5 29.1 6.6": ["quislings"], "3.8 9.4 4.5": ["deodorize"], "15.6 7.8 1.6": ["jilting"], "2.6 20.2 -0.8": ["unmake"], "5.0 2.0 12.9": ["wordpress"], "-4.7 6.0 10.1": ["urokinase"], "-0.7 16.4 6.9": ["wheelman"], "11.0 2.0 8.2": ["appliqued"], "6.4 7.2 5.4": ["openess"], "13.2 19.9 15.4": ["venoms"], "6.8 13.6 7.4": ["epigenome"], "-5.3 3.9 12.7": ["competive"], "6.2 1.1 14.0": ["tuffs"], "-7.0 -1.2 0.6": ["preamps"], "6.9 3.7 13.7": ["nic"], "11.9 2.1 23.7": ["harbourfront"], "5.2 8.4 27.0": ["catkins"], "10.3 14.2 19.9": ["tridents"], "3.1 15.1 17.5": ["lithosphere"], "-5.7 0.7 -1.7": ["disaffiliated"], "13.5 -3.9 12.6": ["ayear"], "10.7 1.8 7.3": ["misselling"], "10.3 19.0 17.5": ["lassies"], "-4.7 14.2 12.4": ["overager"], "-1.8 5.5 11.3": ["jk"], "-2.2 1.3 4.1": ["xchange"], "-3.6 11.7 8.7": ["ministership"], "9.6 7.0 16.5": ["partakers"], "-2.9 -3.1 -4.4": ["dimissed"], "-3.3 15.1 6.2": ["medevaced"], "12.7 4.7 19.8": ["fleecy"], "1.3 3.5 4.3": ["metropolitans"], "12.8 1.8 3.4": ["bunged"], "10.5 7.1 10.9": ["bubblers"], "11.1 3.1 -0.2": ["rorted"], "1.9 11.8 -4.3": ["operationalizing"], "-2.5 8.6 22.0": ["kiteboarders"], "1.0 20.6 9.0": ["slaveholder"], "7.4 1.7 2.3": ["haemorrhaged"], "10.3 8.3 -1.9": ["customizer"], "-5.2 5.1 11.3": ["banjoist"], "0.9 -3.1 -3.0": ["arrangments"], "2.3 8.0 9.7": ["ked"], "5.5 39.8 5.1": ["kuffar"], "4.7 7.5 1.4": ["reassigns"], "-10.5 10.9 7.4": ["promotable"], "10.3 4.6 -5.7": ["midwifed"], "3.1 10.2 11.8": ["chroma"], "18.2 8.6 11.8": ["starbursts"], "-12.5 2.5 8.4": ["utilizations"], "6.1 5.0 7.5": ["midprice"], "0.7 9.7 5.6": ["ethnographer"], "3.1 19.0 18.7": ["crossface"], "-2.8 -0.0 22.2": ["yearround"], "11.9 16.6 8.8": ["poltergeists"], "3.1 6.8 22.2": ["emulsify"], "-3.3 5.0 -2.3": ["unproblematic"], "9.2 6.0 13.6": ["labradoodle"], "6.7 -2.1 -0.4": ["vernakalant"], "11.3 8.6 14.8": ["caking"], "-0.7 40.2 4.6": ["artilleryman"], "9.6 2.1 8.8": ["outgrowths"], "5.0 17.2 12.4": ["rhinoviruses"], "1.2 16.3 4.9": ["interruptive"], "8.4 6.5 7.1": ["rc"], "2.0 12.7 3.1": ["gimmie"], "-1.8 6.8 8.0": ["fastidiousness"], "1.4 6.5 18.9": ["soi"], "6.9 6.2 4.8": ["lobotomies"], "-1.0 11.8 5.3": ["contractile"], "14.6 4.4 4.4": ["clomping"], "10.3 18.5 18.4": ["spork"], "5.5 13.5 9.1": ["conformations"], "6.1 12.6 9.4": ["snogged"], "2.9 13.0 1.9": ["decrypts"], "5.8 11.7 0.2": ["relocatable", "misfirings"], "-1.2 21.5 0.1": ["assaulters"], "7.7 -5.4 15.8": ["tate"], "-3.8 4.3 26.2": ["pullets"], "15.5 7.9 8.1": ["ninnies"], "-0.3 3.4 3.7": ["mmbbls"], "9.8 17.7 12.6": ["snivelling"], "-2.6 6.0 -2.1": ["btu"], "-1.2 12.8 12.7": ["singledom"], "10.9 6.6 32.0": ["tikka"], "3.5 -1.3 6.3": ["ipm"], "5.6 13.1 1.4": ["uncoachable"], "12.7 11.4 -3.3": ["superteam"], "21.1 -0.8 21.5": ["hairnets"], "18.7 9.5 3.5": ["froma"], "17.7 15.7 15.8": ["rapacity"], "-2.5 2.4 4.8": ["unchaperoned"], "10.6 5.9 16.5": ["cubing"], "11.8 8.6 7.3": ["metaverse"], "2.0 4.8 9.6": ["tonsured"], "-8.5 12.3 6.8": ["unadoptable"], "10.2 6.1 6.8": ["astrobiologists"], "-1.5 5.2 -1.5": ["hadn"], "-4.3 11.1 -0.9": ["resile"], "7.9 -1.2 10.5": ["dulcimers"], "0.5 -0.2 7.0": ["methylhexaneamine"], "-2.3 17.2 19.2": ["toolpath"], "3.4 -4.6 8.0": ["fingerplays"], "-3.5 20.0 4.3": ["gainsay"], "5.1 -0.5 1.1": ["assitance"], "15.4 6.8 6.8": ["starbucks"], "0.4 12.7 10.4": ["straitjacketed"], "1.5 6.7 22.8": ["chapatis"], "11.3 1.2 16.5": ["bobbins"], "5.7 11.9 2.8": ["inapt"], "-0.7 0.6 3.2": ["transcoded"], "16.9 17.4 5.5": ["cretinous"], "-5.8 3.6 5.1": ["inurnment"], "-5.4 5.2 8.5": ["tmc"], "-1.3 6.2 4.1": ["catatonia"], "3.3 24.4 0.8": ["indivisibility"], "7.6 10.3 8.9": ["freakiest"], "-2.5 2.7 1.4": ["tofacitinib"], "2.9 7.3 39.4": ["marten"], "-2.3 8.3 8.9": ["timeshift", "orthophoto"], "4.8 13.1 7.5": ["encyclopaedic"], "9.3 -1.4 15.3": ["handwoven"], "6.4 0.6 20.7": ["malunggay"], "4.5 8.7 13.7": ["autodesk"], "1.7 26.2 6.2": ["unrighteousness"], "-2.4 4.6 6.3": ["bafetinib"], "2.8 3.5 3.0": ["towelettes"], "2.3 7.0 6.4": ["adda", "surprsingly"], "16.1 10.9 7.0": ["hieroglyphic"], "3.0 11.7 3.1": ["mollycoddling"], "7.9 16.9 8.9": ["algorithmically"], "-2.2 6.3 10.6": ["homebrewers"], "6.9 -4.7 11.2": ["shortenings"], "9.3 5.3 2.9": ["worden"], "6.9 4.7 10.3": ["fri"], "7.9 6.4 21.9": ["eyedropper"], "17.7 5.0 5.5": ["wildcatter"], "2.2 4.5 7.2": ["transitway"], "6.2 16.9 9.3": ["syllogism"], "-0.1 -0.0 11.4": ["chanter"], "-1.4 4.1 2.5": ["collegially"], "1.9 13.1 14.5": ["bollocking"], "-4.3 6.5 2.7": ["temsirolimus"], "6.1 2.8 14.1": ["tonier"], "16.4 13.6 26.3": ["frond"], "-0.2 19.5 4.9": ["philosphy"], "2.9 14.0 6.4": ["fathomable"], "10.9 7.9 7.0": ["resizable"], "19.3 3.9 10.7": ["privatizes"], "-3.0 6.3 25.7": ["waterbody"], "9.6 15.8 2.4": ["counterintuitively"], "8.9 19.9 21.2": ["bilges"], "0.0 9.5 2.0": ["fanclub"], "-1.9 6.4 -0.8": ["contextualised"], "17.6 7.3 12.7": ["spectacled"], "-9.8 10.5 7.6": ["mikveh"], "22.0 19.2 15.5": ["sunbeams"], "5.5 6.6 2.6": ["twitterers"], "1.1 5.1 14.6": ["enteric"], "13.1 0.0 17.7": ["coronet"], "6.2 7.7 14.8": ["sinecures"], "3.1 6.0 13.5": ["seediness"], "1.4 10.1 13.0": ["miscasting", "slangy"], "2.6 -5.5 1.8": ["perent"], "1.5 14.4 12.7": ["reproof"], "13.1 10.9 32.2": ["hornbill"], "8.4 3.8 14.9": ["nonlocal"], "-2.3 13.5 4.1": ["eid"], "5.0 -7.8 5.0": ["tol"], "12.8 4.5 6.4": ["lopes"], "9.0 21.6 6.9": ["unstoppably"], "7.1 17.6 -3.8": ["tribunes"], "1.3 1.1 6.2": ["sweatsuits"], "23.2 5.6 27.9": ["toadstools"], "-1.9 -1.0 8.6": ["postbag"], "-3.3 -2.9 14.1": ["naging"], "4.8 12.0 8.8": ["animatics"], "4.6 7.6 2.7": ["tamarins"], "4.2 13.7 1.6": ["alll"], "2.9 7.8 6.8": ["downwinders"], "13.0 3.6 11.1": ["thumbscrews"], "15.8 15.7 5.2": ["numbly"], "1.3 15.4 14.9": ["gridlocks"], "15.8 13.1 18.4": ["worktop"], "12.4 11.5 -3.2": ["technologic"], "-4.3 14.5 4.9": ["wingbacks"], "10.6 12.1 11.4": ["palimpsest"], "1.2 16.7 13.9": ["hangingwall"], "9.5 5.7 19.8": ["tache"], "1.6 7.2 10.0": ["helices"], "9.3 25.7 13.3": ["backstabber"], "2.5 11.4 -1.0": ["insistance"], "-1.5 2.2 13.6": ["dendrite"], "7.6 6.4 5.7": ["undercapitalised"], "-6.1 2.7 0.4": ["wbf"], "5.7 11.0 46.2": ["burbot"], "15.6 9.8 16.4": ["crumbing"], "7.6 2.1 8.8": ["stitchers"], "3.5 10.7 7.6": ["snick"], "-8.3 -1.6 6.5": ["motets"], "2.8 8.8 1.6": ["auroral"], "-0.2 4.7 7.6": ["sclerotherapy"], "-9.0 17.3 8.4": ["clearheaded"], "-1.4 8.9 11.8": ["jells"], "-6.8 7.3 2.5": ["frum"], "15.4 10.1 11.2": ["drearily"], "8.1 10.7 -3.4": ["localizations"], "2.1 9.4 12.0": ["kinesin"], "6.8 20.1 22.4": ["scalawags"], "14.0 -0.9 30.3": ["mooncake"], "-1.4 10.1 14.8": ["bumiputeras"], "22.9 -1.6 9.1": ["hoovered"], "-2.3 -0.9 -2.8": ["saud"], "7.2 -3.1 3.4": ["advergames"], "-6.9 0.3 2.0": ["mesalamine"], "15.3 34.6 11.9": ["stormtrooper"], "9.0 4.1 3.7": ["coarsened"], "2.3 11.6 2.2": ["adenine"], "3.5 3.6 12.8": ["gentamicin"], "4.9 6.9 18.2": ["jetboat"], "-0.1 10.2 16.3": ["tamiflu"], "16.1 8.3 9.6": ["emboss"], "16.1 3.4 33.3": ["crumbed"], "9.0 13.7 10.1": ["ripcord"], "-1.5 9.7 13.5": ["microflora"], "3.7 1.6 -1.5": ["scrutineer"], "5.4 18.9 8.5": ["scramblers"], "17.9 5.2 4.2": ["wonderboy"], "-4.9 20.2 2.8": ["lastingly"], "7.7 14.9 6.5": ["braindead"], "-6.2 1.9 2.0": ["indictors"], "-0.5 4.9 11.8": ["alkylate"], "-1.1 3.2 10.4": ["followthrough"], "3.7 7.3 10.8": ["coll"], "-3.0 8.0 23.3": ["zinfandels"], "4.6 -3.1 -1.0": ["nma"], "1.7 7.0 9.6": ["overdub", "prelature", "preguntas"], "9.5 8.8 16.4": ["eww"], "-1.0 0.9 7.6": ["gh"], "2.8 6.5 5.4": ["footbed"], "-6.4 6.8 4.1": ["retinoid"], "-5.1 6.5 17.0": ["craftsperson"], "9.8 13.6 15.6": ["spim"], "-5.1 13.4 11.3": ["overgrazed"], "-3.5 13.6 -0.3": ["falsifies"], "8.4 -3.4 11.5": ["underwhelm"], "14.0 8.8 17.7": ["floaties"], "-2.2 12.7 20.6": ["anthracnose"], "10.1 14.3 7.7": ["enviornment"], "8.5 21.4 4.9": ["doublethink"], "2.4 8.3 9.1": ["sensuousness"], "4.1 6.7 8.8": ["rebirthing"], "11.9 21.5 6.5": ["disrupters"], "11.1 15.9 1.0": ["germy"], "13.6 5.5 8.0": ["leatherwork"], "-8.5 17.0 31.1": ["chukar"], "-2.2 10.5 6.1": ["transsexuality"], "9.5 2.5 2.5": ["colorado"], "3.2 17.5 0.5": ["raptured"], "9.3 11.9 6.0": ["krypton"], "-7.1 22.0 0.3": ["commandants"], "-4.6 14.4 -2.8": ["hinderance"], "0.2 6.3 0.0": ["manhours"], "15.2 1.2 15.0": ["papermakers"], "7.8 2.7 21.6": ["carte"], "-10.7 6.5 2.2": ["intensivist"], "8.9 7.6 11.3": ["flirtatiously"], "-1.1 10.3 8.4": ["miscommunicated"], "3.6 5.7 22.0": ["caipirinha"], "10.2 8.5 10.9": ["thumpers"], "0.4 28.5 4.5": ["maoists"], "11.9 5.1 7.8": ["geophones"], "4.5 8.1 11.9": ["danny"], "7.7 4.5 39.6": ["broccolini"], "10.2 -1.8 11.4": ["leas"], "2.9 -0.0 -7.7": ["cardiorespiratory"], "-6.6 3.4 10.3": ["pret"], "-2.4 7.9 6.5": ["resolver"], "-1.0 4.1 -7.5": ["beleived"], "7.4 10.3 19.1": ["jamb"], "12.0 3.7 21.0": ["mohawked"], "19.3 6.7 22.2": ["soothsaying"], "7.8 10.0 0.7": ["antistatic"], "-0.5 5.6 5.0": ["dyspraxia"], "5.0 3.4 6.0": ["fc"], "6.2 13.1 8.7": ["poundings"], "-8.1 6.8 4.9": ["intensivists"], "22.0 12.4 13.1": ["truckmakers"], "11.2 4.2 7.3": ["tantalise"], "10.1 6.7 8.1": ["trenchcoats"], "8.3 24.0 26.1": ["adelgid"], "4.4 1.9 4.1": ["bishopric"], "14.8 7.6 11.4": ["whistlers"], "2.6 11.0 3.7": ["ereaders"], "1.7 13.8 7.0": ["hal"], "8.4 11.5 14.9": ["korean"], "0.3 16.4 31.3": ["thermocline"], "11.5 11.4 18.1": ["transfat"], "2.2 -0.2 18.1": ["festa"], "-5.4 4.0 6.9": ["titah"], "-1.7 6.7 1.4": ["reregistered"], "10.9 2.9 34.7": ["gingery"], "-12.5 9.2 4.8": ["diarrheal"], "3.7 9.0 13.3": ["babyhood"], "-11.1 16.8 8.8": ["ecclesiology"], "17.2 20.8 17.4": ["mammon"], "7.5 5.0 10.2": ["reimaging"], "4.3 18.7 4.4": ["suggestible"], "6.8 31.9 11.2": ["unreason"], "8.2 4.5 24.2": ["cowbirds"], "19.5 8.1 18.8": ["tchotchke"], "1.1 11.7 5.6": ["demarcates"], "-1.3 6.2 29.3": ["shochu"], "13.7 10.2 3.4": ["syn"], "5.3 7.2 14.2": ["harris"], "1.2 3.9 -6.4": ["acclaims"], "2.5 22.5 8.0": ["brigandage"], "-8.6 8.9 8.9": ["osteoporotic"], "7.3 -2.6 13.1": ["wedi"], "9.9 13.7 11.7": ["tmz"], "5.6 1.2 5.7": ["leur"], "11.1 6.5 12.7": ["hemi"], "3.8 34.2 9.4": ["idolaters"], "3.8 16.8 17.1": ["alphas"], "-3.7 14.9 0.8": ["transphobia"], "3.1 2.8 33.2": ["rudd"], "15.9 1.0 15.1": ["papas"], "5.2 12.2 -1.7": ["contigent"], "6.2 16.1 6.3": ["flustering"], "-5.4 5.1 2.4": ["refundings"], "5.3 0.5 1.6": ["covergirl"], "5.0 1.0 17.5": ["stubbies"], "-1.0 10.8 4.4": ["generalising"], "-1.1 3.2 1.7": ["consanguinity"], "-18.1 6.3 3.5": ["palliation"], "6.6 7.6 14.4": ["loamy"], "8.1 7.2 8.4": ["immodestly"], "9.5 16.8 7.2": ["cablecos"], "19.6 12.2 20.4": ["splotched"], "3.4 14.1 17.9": ["sens"], "-0.4 -4.5 15.3": ["pst"], "4.0 8.5 10.7": ["misfield"], "0.8 8.9 10.3": ["pliability"], "12.4 18.4 11.6": ["windbags"], "-0.1 19.3 -0.7": ["aggrandize"], "11.6 4.6 46.6": ["smelts"], "-0.6 3.3 7.5": ["appendixes"], "7.0 0.3 -2.1": ["warrantees"], "1.2 13.7 7.5": ["ryong"], "7.1 11.1 10.5": ["catnaps"], "-3.0 11.7 5.9": ["neoplastic"], "0.5 9.0 11.7": ["clit"], "4.8 8.3 1.5": ["cadastre"], "3.1 -1.7 1.6": ["cassation"], "3.2 2.7 14.9": ["semiformal"], "0.9 5.8 15.3": ["diploid"], "5.7 8.9 4.8": ["baseballers"], "7.7 12.5 6.0": ["bewitch"], "-5.5 -5.2 2.1": ["learnership"], "-2.3 9.9 12.3": ["intersquad"], "4.4 9.2 2.8": ["visiongain"], "-1.2 7.2 1.8": ["ceftaroline"], "10.2 9.4 2.9": ["misplaces"], "2.5 14.4 10.2": ["schizo"], "-1.6 11.9 8.6": ["chartist"], "2.8 26.7 3.4": ["refusenik"], "-10.2 13.5 2.2": ["pneumonias"], "5.0 12.4 5.4": ["customisations"], "-5.0 5.6 2.9": ["allottee"], "5.1 17.4 7.8": ["deformable"], "18.8 9.6 19.8": ["teakettle"], "2.9 4.8 9.2": ["departmentwide"], "-1.9 -0.7 9.5": ["rideshare"], "0.2 4.5 4.2": ["neuralgia"], "5.1 11.6 7.3": ["fortissimo"], "3.9 7.3 4.6": ["superfluidity"], "-1.4 4.0 21.5": ["sauvignon"], "2.7 16.2 5.1": ["roleplayers"], "9.2 5.0 0.9": ["spectrometry"], "1.2 -2.1 7.1": ["scaleback"], "6.0 -3.6 6.6": ["blvd"], "-8.1 20.5 0.9": ["surveillances"], "3.9 8.1 7.3": ["crizotinib"], "-2.5 -3.5 6.5": ["neuropathologist"], "0.3 11.7 31.2": ["cottontails"], "13.3 7.0 9.9": ["aftermarkets"], "2.1 13.3 11.3": ["dicker"], "-6.2 10.7 7.3": ["xxiii"], "4.4 14.8 11.6": ["bugling"], "7.7 3.8 12.4": ["angularity"], "5.4 3.5 8.4": ["freeholds"], "8.4 12.1 10.6": ["philanderers"], "-6.3 13.4 2.1": ["reengagement"], "9.1 11.8 10.8": ["relabeling"], "8.7 9.0 14.4": ["landform"], "-2.8 -4.1 3.6": ["tbc"], "1.0 1.1 8.4": ["ppc"], "-4.9 9.0 1.9": ["militated"], "-2.1 3.3 1.4": ["maintainence"], "-3.8 11.3 7.6": ["aerobically"], "6.6 4.7 14.3": ["headstand"], "0.0 1.8 10.7": ["ami"], "5.8 2.1 5.3": ["porque"], "10.7 15.8 19.8": ["congealing"], "-1.8 11.2 16.9": ["stockmen"], "11.2 6.2 10.3": ["presumable"], "9.1 1.9 8.9": ["rhapsodizing"], "6.2 8.1 15.5": ["totty"], "5.8 3.6 1.5": ["hybris"], "2.9 -7.6 7.0": ["wavier"], "-4.4 16.6 15.9": ["cutman"], "-3.2 13.0 7.9": ["integrins"], "-3.6 0.7 3.9": ["bronchoconstriction"], "11.9 9.5 1.4": ["workrooms"], "4.8 17.2 7.1": ["extorts"], "1.7 9.0 1.5": ["definatly"], "-12.6 5.3 0.6": ["elaborations"], "8.0 11.2 14.5": ["spatters"], "11.7 23.3 13.2": ["artifices"], "5.9 8.0 32.8": ["laker"], "29.2 3.5 5.3": ["skyscraping"], "0.0 3.6 14.3": ["flatwater"], "9.4 17.3 8.6": ["whinger"], "18.5 9.6 5.4": ["stakebuilding"], "6.1 18.2 6.9": ["constabularies"], "1.6 3.5 27.1": ["rices"], "6.2 3.2 11.6": ["ejp"], "7.5 -1.1 42.9": ["crudo"], "-3.1 11.7 0.6": ["femicide"], "-0.2 3.7 0.8": ["interdealer"], "0.4 5.8 13.1": ["pastern"], "6.8 7.9 7.2": ["improbabilities"], "19.5 10.5 10.7": ["tron"], "10.0 6.2 4.7": ["togther"], "-1.8 1.8 5.0": ["saleability"], "3.7 -3.7 3.6": ["ruh"], "-2.0 3.6 0.9": ["ence"], "10.1 4.1 16.6": ["breakfasting"], "1.7 15.0 11.0": ["bedouin"], "11.4 15.3 12.5": ["ransomware"], "22.1 7.4 16.4": ["tubed"], "4.3 3.7 6.8": ["dragway"], "8.0 2.0 22.7": ["capuchins"], "14.1 6.3 12.8": ["salesclerk"], "-0.5 2.8 17.8": ["halau"], "13.7 5.5 3.1": ["suckled"], "7.9 16.5 6.6": ["disembarks"], "10.3 2.3 -5.9": ["lastyear"], "-0.4 3.8 13.8": ["moissanite"], "-0.4 2.0 10.4": ["budded"], "13.6 16.0 32.8": ["oozy"], "11.3 0.5 11.6": ["scottish"], "1.4 10.7 11.7": ["meso"], "8.6 15.5 26.1": ["fufu"], "-4.9 16.7 3.7": ["incorrectness"], "4.7 10.2 15.3": ["kappa"], "3.3 -2.4 11.2": ["laminators"], "5.1 7.9 12.3": ["honda"], "-9.6 8.8 6.3": ["microstamping"], "7.7 13.5 12.9": ["unzips"], "9.1 13.9 5.5": ["eliminators"], "8.4 2.7 1.8": ["typesetter"], "2.7 3.3 12.6": ["kyats"], "9.8 20.9 -0.4": ["acquiror"], "14.1 13.1 8.3": ["hellion"], "-0.5 7.4 3.5": ["saids"], "0.5 2.1 9.4": ["pawnbroking"], "7.8 9.3 2.2": ["pn"], "2.7 1.6 6.4": ["etnies"], "7.6 3.8 7.7": ["sportsbetting"], "9.5 9.6 16.2": ["squeakers"], "-3.0 7.2 6.2": ["compositionally"], "11.9 16.8 0.4": ["recluses"], "-0.3 11.3 27.9": ["longboat"], "-0.2 3.8 16.5": ["skifield"], "-0.3 11.5 6.1": ["emboli"], "-0.4 16.6 16.0": ["mattes"], "3.7 1.2 7.8": ["zeolites"], "4.4 7.5 5.6": ["recalculates"], "4.8 16.8 5.2": ["vetos"], "-6.5 10.9 0.4": ["hypokalemia"], "-0.7 6.2 8.7": ["epoetin"], "6.6 16.0 0.7": ["coaltion"], "5.4 4.9 17.7": ["loafs"], "3.5 15.5 6.6": ["burry"], "1.7 1.0 3.6": ["dissatisfactions"], "-1.1 -7.0 6.8": ["nonsubscribers"], "-2.4 14.8 9.7": ["fording"], "8.6 0.2 41.0": ["shiitakes"], "11.6 13.2 1.6": ["ue"], "2.8 14.3 3.9": ["slipups"], "1.7 1.8 2.3": ["alogliptin"], "4.3 13.5 -2.9": ["damningly"], "1.8 9.1 9.5": ["transposes"], "0.4 -1.4 2.3": ["forsees"], "4.8 -0.4 8.5": ["reinspect"], "2.6 12.0 13.7": ["snobbishness"], "-3.2 8.9 3.9": ["cerebellar"], "-6.5 3.6 -0.1": ["bronchospasm"], "-15.2 9.4 7.5": ["fiqh"], "2.2 8.4 3.2": ["gamification"], "-0.4 6.1 8.4": ["hardpressed"], "-1.4 9.4 9.8": ["immunogen"], "-0.6 4.7 10.0": ["poss"], "0.7 4.7 11.2": ["inseam"], "12.7 8.1 18.8": ["sifter"], "11.8 14.7 9.9": ["neta"], "4.0 4.3 15.2": ["fibroblast"], "3.0 11.3 23.2": ["nesters"], "2.2 1.3 3.6": ["reboarded"], "7.1 5.9 14.2": ["wey"], "4.0 14.1 6.8": ["adjustor"], "10.7 13.8 7.4": ["egypt"], "5.7 20.1 2.3": ["suzerainty"], "20.9 13.2 7.4": ["wizardly"], "-7.6 10.3 -0.7": ["derogate"], "9.6 41.9 1.8": ["undefeatable"], "2.6 -2.1 2.5": ["nts"], "1.6 -0.3 12.9": ["lok"], "5.9 18.0 6.9": ["militaria"], "5.7 11.7 21.2": ["plancha"], "5.4 24.6 7.7": ["moonbat"], "23.6 19.8 37.3": ["barracudas"], "3.0 5.5 3.2": ["priviledged"], "-9.4 8.2 -1.7": ["talkbacks"], "3.5 11.3 14.0": ["smirky"], "9.3 1.5 0.6": ["premedia"], "7.3 20.8 20.4": ["moonstone"], "-5.2 7.3 13.5": ["aspirate"], "-6.5 5.5 -2.9": ["postulator"], "-1.2 13.1 2.1": ["irrelevent"], "1.3 10.3 3.8": ["hw"], "11.0 -1.9 -3.1": ["reseach"], "14.4 4.6 15.2": ["undulated"], "1.7 10.8 8.9": ["schlubby"], "-1.0 8.3 34.4": ["mortadella"], "5.4 15.5 5.6": ["adrenalized"], "-6.8 7.0 5.7": ["perimenopausal"], "-1.3 6.8 9.8": ["butyl"], "-0.0 -0.8 6.5": ["multiunit"], "0.4 16.8 4.0": ["idealizing"], "0.7 17.5 2.9": ["blasphemed"], "5.4 24.8 15.3": ["blabbermouth"], "13.8 12.1 15.0": ["frontyard"], "3.8 2.7 5.0": ["degassing"], "-1.1 9.0 8.7": ["tradesperson"], "4.1 6.7 -0.0": ["baghouse"], "7.1 6.6 0.8": ["dudded"], "12.9 18.6 24.2": ["cockfighters"], "16.3 6.4 10.3": ["leonine"], "11.4 16.9 21.0": ["maya"], "11.8 18.1 7.9": ["sweepingly"], "-5.1 11.4 11.3": ["mohalla"], "21.4 12.6 31.5": ["fishhook"], "0.0 -0.4 13.6": ["smallholdings"], "6.0 3.4 10.5": ["toweled"], "-0.9 7.7 9.5": ["ghar"], "11.2 20.8 9.1": ["sleepwalker"], "4.8 1.5 12.2": ["gcc"], "-7.0 15.6 7.1": ["matchwinners"], "-12.9 6.5 6.1": ["detainers"], "3.9 5.4 6.9": ["degreasers"], "7.6 10.2 8.7": ["etal"], "10.8 -3.0 8.7": ["liniment"], "2.2 17.6 2.4": ["corollaries"], "10.3 19.8 16.2": ["slapshots"], "6.9 -1.5 16.8": ["bandeau"], "7.7 9.7 17.1": ["lef"], "3.8 5.4 11.2": ["falsettos"], "-1.8 0.5 -1.1": ["aquitted"], "14.2 8.6 13.6": ["somnambulant"], "0.8 6.4 24.8": ["ragi"], "8.4 1.1 8.8": ["rappin"], "-6.0 12.5 9.3": ["fatherlessness"], "9.6 9.8 -1.2": ["ululations"], "0.8 8.7 7.7": ["somberness"], "8.1 -3.6 0.2": ["qu"], "5.3 2.3 9.0": ["wallcovering"], "9.7 -1.3 4.7": ["nvidia"], "5.3 10.3 7.2": ["morphologies"], "-4.9 -5.8 7.1": ["cablecast"], "8.3 17.2 37.5": ["ptarmigan"], "8.7 18.3 10.2": ["newspeak"], "7.3 9.0 6.9": ["alikes"], "17.5 18.4 14.4": ["blackens"], "11.4 7.9 8.4": ["accrete"], "4.5 5.8 6.2": ["looong"], "14.8 6.8 14.6": ["woodcraft"], "-4.3 7.5 -0.1": ["individualizing"], "21.4 10.3 15.2": ["runts"], "-6.8 9.9 23.7": ["bareboat"], "14.7 2.4 0.6": ["jacuzzis"], "9.9 12.3 17.4": ["muon"], "-0.8 3.0 1.6": ["endif"], "6.1 18.2 20.7": ["durrrr"], "16.8 15.0 21.9": ["zephyr"], "-3.0 12.8 3.8": ["neccesary"], "4.6 5.0 8.2": ["consolidative"], "-9.9 -0.5 2.5": ["akathisia"], "7.8 27.2 5.6": ["jailbreakers"], "0.7 22.4 14.8": ["dogfighters"], "2.5 10.4 3.8": ["discomforted"], "-8.9 10.7 3.5": ["contextualization"], "-1.1 14.8 4.4": ["unmaintained"], "9.5 -0.9 15.2": ["pomade"], "4.4 4.5 9.7": ["vasodilation"], "2.6 1.9 20.1": ["chloramphenicol"], "20.7 6.2 12.2": ["bellweather"], "-3.4 -0.4 7.7": ["aligners"], "0.1 8.4 6.6": ["waked"], "3.4 15.8 6.1": ["worthiest"], "6.3 2.0 4.8": ["mascaras"], "-1.9 5.5 5.3": ["stomatitis"], "9.5 0.8 5.0": ["ultrafine"], "9.7 11.4 11.7": ["interlace"], "7.4 3.8 7.8": ["vas"], "13.1 10.6 20.0": ["eucalypts"], "1.8 0.4 11.5": ["absorbents"], "11.8 30.4 17.7": ["badasses"], "16.7 9.6 13.7": ["punny"], "6.9 -2.6 9.1": ["rasing"], "-6.7 12.0 4.0": ["supercentenarians"], "1.6 2.1 7.0": ["grandnieces"], "2.8 7.9 17.2": ["steeplechasing"], "6.1 -1.9 3.3": ["avril"], "4.3 9.9 12.6": ["unembarrassed"], "-6.8 8.4 2.1": ["carreer"], "19.4 6.6 22.3": ["ovoid"], "15.0 18.2 11.1": ["inelegantly"], "5.8 1.8 7.6": ["guilders"], "-0.9 0.4 1.4": ["bodyshop"], "6.0 10.0 12.6": ["bizarreness"], "-0.6 0.4 12.1": ["parkinsonism"], "8.9 12.0 13.1": ["silva"], "6.1 18.8 7.6": ["subterfuges"], "-4.7 -2.0 -3.8": ["sourcebook"], "-1.0 -1.9 9.8": ["relaxer"], "-0.1 10.1 5.9": ["intermixing"], "22.5 0.7 5.8": ["bourgeoning"], "3.3 -1.7 0.8": ["multicentre"], "1.2 7.8 4.2": ["shehnai"], "-0.4 5.7 10.0": ["prefabrication"], "-5.5 9.5 16.4": ["astringency"], "-3.1 13.8 7.8": ["inapposite"], "-6.3 10.1 7.3": ["explicitness"], "23.2 15.0 9.2": ["huger"], "4.5 12.4 2.5": ["positron"], "6.0 6.4 14.0": ["feminisation"], "1.0 7.1 16.5": ["sidesplitting"], "-6.8 3.7 9.9": ["subregions"], "3.2 4.5 7.8": ["bootup"], "13.8 7.5 13.2": ["gasfields"], "-7.6 7.9 -4.1": ["utca"], "18.6 11.3 8.5": ["manu"], "-2.1 16.0 12.7": ["lgbt"], "4.8 -0.9 16.2": ["blanche"], "3.2 6.1 5.1": ["reconstitutes"], "-3.1 3.6 10.0": ["myelination"], "17.7 7.7 7.0": ["zaniest"], "1.9 8.4 15.1": ["exfoliant"], "2.4 4.0 9.1": ["toplined"], "-4.2 6.4 46.4": ["canvasbacks"], "-6.8 4.0 8.9": ["thyroxine"], "-9.8 1.5 2.7": ["spironolactone"], "0.2 1.9 6.8": ["microstock"], "-3.5 -1.4 2.3": ["passings"], "0.3 15.8 9.5": ["coupledom"], "-5.0 6.3 12.4": ["shorthaul"], "4.2 4.9 1.1": ["disquieted"], "5.8 4.5 -5.6": ["curently"], "1.4 6.7 13.6": ["mesenchymal"], "1.2 2.9 16.5": ["interglacial"], "0.9 5.4 -2.1": ["indemnifications"], "10.5 -1.0 8.8": ["outlaid"], "3.1 8.5 25.2": ["reefers"], "-7.0 1.3 2.8": ["lansoprazole"], "11.9 14.9 16.1": ["ragamuffin"], "10.5 24.5 17.7": ["punisher"], "2.9 6.7 7.5": ["philippines"], "12.9 10.5 10.0": ["hypodermic"], "12.6 6.8 18.7": ["hardboard"], "-0.0 11.2 -4.7": ["coopted"], "-1.1 6.3 1.8": ["heartens"], "-1.6 4.0 5.4": ["candesartan"], "-3.5 6.1 3.9": ["aetiology"], "6.6 2.3 1.7": ["reclassifies"], "-0.6 9.7 13.8": ["supplementally"], "0.5 4.3 8.8": ["snowboarded"], "5.0 6.2 31.4": ["bulgogi"], "-1.6 -4.5 6.4": ["webcasted"], "0.2 18.1 4.9": ["scruple"], "2.6 10.4 14.3": ["hubbies"], "5.6 24.2 17.4": ["sunrays"], "11.2 43.2 11.4": ["ambushers"], "-8.6 -3.5 8.9": ["childminding"], "-1.1 20.1 15.9": ["tazer"], "-0.1 23.6 5.1": ["coercively"], "4.0 0.0 15.5": ["bata"], "16.2 13.2 10.7": ["doomsayer"], "0.7 8.3 2.1": ["immobilisation"], "4.7 8.5 -0.0": ["refound"], "11.0 6.2 11.8": ["apres"], "3.2 -3.3 -1.6": ["prebook"], "6.8 13.5 11.4": ["foremothers"], "0.6 -0.2 7.8": ["yucks"], "8.5 3.0 6.2": ["graffitti"], "1.1 1.3 3.2": ["contributers"], "20.1 11.1 5.5": ["unshackling"], "-7.4 5.4 7.4": ["postions"], "21.6 1.0 17.1": ["curlicue"], "7.8 0.1 12.0": ["poli"], "2.5 6.3 23.3": ["gharials"], "7.0 5.5 17.1": ["neolithic"], "4.4 9.2 8.6": ["twisties"], "8.9 15.5 10.0": ["looooong"], "1.6 12.7 19.0": ["scabbed"], "5.0 1.8 3.4": ["merci"], "0.1 17.4 10.8": ["outbattled"], "-0.9 18.7 12.0": ["conventionality"], "-3.1 6.7 16.1": ["jazzmen"], "4.0 17.2 17.3": ["plainness"], "-4.1 13.4 3.8": ["evenhandedly"], "4.5 18.1 11.1": ["syncretism"], "6.0 10.0 8.5": ["footmarks"], "3.2 -8.4 1.9": ["administrates"], "16.2 17.7 11.8": ["firelight"], "2.1 5.3 7.6": ["winglet"], "-2.5 5.9 10.5": ["osteocalcin"], "9.5 22.4 6.0": ["unkindness"], "5.4 12.6 17.5": ["sharon"], "1.0 25.7 2.0": ["incapacitates"], "8.3 10.9 12.3": ["spaceports"], "1.6 9.3 24.2": ["aloo"], "11.7 14.9 10.1": ["ranters"], "-3.8 22.2 12.9": ["freewill"], "16.0 7.7 19.6": ["yews"], "4.4 -2.2 3.8": ["aac"], "2.3 10.5 33.9": ["seagrasses"], "-1.3 18.7 3.2": ["racialism"], "11.9 9.6 9.1": ["soother"], "-2.8 -0.9 -1.4": ["impleaded"], "-8.6 3.3 7.6": ["virological"], "3.6 9.2 13.6": ["nancy"], "-0.6 8.0 11.1": ["godparent"], "12.7 15.9 16.9": ["planers"], "12.3 3.0 6.3": ["boogying"], "13.6 -3.6 2.9": ["lar"], "-0.4 13.5 3.0": ["flagbearership"], "11.9 14.6 6.7": ["attaboy"], "5.3 10.2 5.0": ["debatably"], "1.9 5.2 6.3": ["methylnaltrexone"], "0.2 0.5 12.9": ["shirtdress"], "-2.3 2.3 12.8": ["iland"], "8.0 11.8 13.7": ["harlots"], "10.1 14.3 23.5": ["stargazer"], "-1.3 -0.6 8.7": ["enrichments"], "9.9 11.0 -0.0": ["barraging"], "4.3 8.8 3.1": ["biogeneric"], "9.4 7.4 11.5": ["mandrel"], "6.7 7.5 5.8": ["rockiest"], "1.7 4.1 3.4": ["incented"], "14.9 18.3 10.3": ["nanomachines"], "3.3 -4.7 14.3": ["nung"], "7.3 16.9 3.1": ["sceptically"], "-5.8 -3.3 -0.0": ["audioconference"], "7.5 6.4 0.8": ["pda"], "1.9 18.9 6.1": ["destructed"], "6.1 17.7 7.1": ["microtargeting"], "6.8 20.3 7.2": ["reenters"], "10.6 1.0 -4.1": ["ofits"], "-0.4 8.8 10.1": ["auriferous"], "2.9 14.8 9.3": ["sayeth"], "14.0 17.4 12.3": ["kissers"], "19.7 -7.8 0.7": ["milliion"], "1.4 15.9 -0.1": ["nonconformists"], "-6.6 -2.5 12.4": ["cohosts"], "2.6 19.2 17.6": ["dragnets"], "14.9 10.9 16.4": ["blackmarket"], "5.6 6.0 28.5": ["panettone"], "-15.0 -3.1 10.6": ["consigners"], "16.4 7.3 29.7": ["eclairs"], "16.5 4.2 2.9": ["piffling"], "4.7 12.5 10.9": ["foggiest"], "5.6 2.6 5.4": ["numberplate"], "10.7 3.8 12.8": ["magnesite"], "7.8 4.1 7.1": ["coltish"], "0.8 9.6 5.1": ["carburettor"], "7.5 -5.9 19.8": ["restauranteurs"], "7.6 1.8 1.0": ["diecast"], "14.5 19.5 13.4": ["poisoner"], "2.8 3.1 -0.3": ["dosent"], "6.4 12.9 11.2": ["rinkside"], "5.9 9.3 -3.8": ["nonintrusive"], "18.2 7.1 17.3": ["thunderbird"], "19.0 9.6 10.7": ["spoilsports"], "4.7 9.0 2.7": ["appaling"], "6.1 10.5 -0.9": ["reconvert"], "-3.5 8.6 -3.4": ["ecallantide"], "13.4 12.9 18.2": ["purty"], "-5.0 5.1 12.9": ["embryogenesis"], "-3.2 10.9 12.1": ["gossypol"], "1.3 1.8 10.2": ["atopy"], "13.9 9.2 13.1": ["hora"], "21.7 13.7 23.2": ["cupids"], "24.5 13.4 36.1": ["pinecone"], "11.0 6.8 25.8": ["comestibles"], "0.6 5.1 3.4": ["esthetically"], "2.2 7.4 8.8": ["bandoneon"], "9.2 9.0 14.6": ["pyramiding"], "1.7 14.9 8.0": ["comradely"], "7.1 -3.8 6.3": ["colones"], "3.8 6.7 5.9": ["stows"], "7.1 13.2 7.7": ["inanely"], "5.4 4.3 14.7": ["igneous"], "5.3 4.9 17.5": ["saya"], "-0.8 -6.3 6.0": ["bte"], "6.2 29.2 9.7": ["narcotraffickers"], "-4.6 7.4 1.1": ["vasodilator"], "13.9 12.9 8.5": ["sundials"], "8.4 3.8 19.7": ["bennies"], "-1.4 6.0 0.8": ["inspectorates"], "1.0 8.9 11.0": ["alpinists"], "21.9 14.1 16.0": ["captcha"], "6.2 2.8 7.9": ["biodegrades"], "-3.2 9.1 3.7": ["oversample"], "4.9 10.6 4.6": ["baptise"], "-1.7 6.0 4.2": ["patentees"], "5.4 17.1 4.1": ["scandalize"], "1.4 16.6 8.7": ["sodomite"], "3.8 14.1 12.7": ["icefall"], "-0.3 11.9 5.5": ["gamewinning"], "19.3 16.1 12.1": ["brainteaser"], "-1.4 -0.2 10.8": ["nicole"], "0.1 7.8 14.3": ["minivehicles"], "-1.2 5.1 12.6": ["pandits"], "-3.2 10.7 2.5": ["unrisked"], "-0.7 27.4 2.9": ["deniable"], "2.3 6.9 12.5": ["tubules"], "11.0 1.9 56.0": ["geoduck"], "1.3 2.6 4.5": ["carparking"], "11.1 12.0 17.1": ["auld"], "-8.9 -2.3 4.8": ["subsitute"], "15.9 5.7 28.3": ["shags"], "3.6 19.5 0.4": ["insurrectionary"], "1.8 6.1 4.5": ["outreaching"], "-2.7 1.1 -0.7": ["intermediated"], "-8.1 8.4 1.6": ["discretions"], "5.6 14.5 11.8": ["deplorably"], "5.6 1.8 18.0": ["mudguards"], "-2.0 7.8 13.1": ["weatherwise"], "2.7 16.7 10.4": ["doorjamb"], "-1.2 8.6 4.8": ["picosecond"], "4.0 11.4 2.7": ["nows"], "9.9 6.3 6.0": ["wal", "sizably"], "10.4 4.5 14.9": ["confectioneries"], "2.8 4.3 0.4": ["timeliest"], "2.8 -1.3 1.1": ["juillet"], "6.5 4.8 7.2": ["nebivolol"], "13.8 11.3 15.3": ["pilasters"], "13.4 15.0 11.8": ["meteoroid"], "14.5 10.9 0.2": ["overhyping"], "11.7 10.3 -2.8": ["efficent"], "-2.0 14.4 7.2": ["unliveable"], "-4.2 5.8 1.9": ["handpieces"], "6.4 13.1 11.8": ["stoutest"], "-0.8 9.4 -3.1": ["woudl"], "-13.2 5.1 -0.1": ["prothrombin"], "17.4 11.8 4.7": ["phrasebook"], "8.6 5.3 8.9": ["recommences"], "6.6 8.7 9.7": ["lindsay"], "8.2 6.8 13.3": ["telehandler"], "-3.7 26.0 6.7": ["sectarians"], "5.2 6.9 6.8": ["attenuators"], "13.6 22.9 10.9": ["whackos"], "-2.1 12.8 -2.5": ["factum"], "-2.1 10.8 7.2": ["axillary"], "2.6 3.0 12.6": ["threshed"], "-1.3 7.8 35.7": ["saugeye"], "3.5 3.0 5.4": ["uteruses"], "8.1 12.4 0.7": ["energises"], "3.3 20.4 7.7": ["prickliness"], "0.3 -0.8 10.4": ["preopening"], "11.8 15.8 19.8": ["rototiller"], "12.5 0.2 10.3": ["goatskin"], "6.7 5.2 9.8": ["shik"], "-3.7 7.0 6.2": ["differnt"], "4.1 8.9 16.8": ["turntablism"], "7.8 6.8 17.9": ["hominins"], "1.2 -0.1 14.7": ["braiders"], "11.0 6.4 13.7": ["tatoos"], "6.0 11.9 9.9": ["chronometer"], "-2.9 5.5 14.0": ["overnighter"], "15.9 2.2 1.9": ["sueing"], "11.7 18.0 5.2": ["gasbag"], "6.1 6.2 7.2": ["salved"], "7.5 1.9 7.3": ["accreditor"], "13.8 8.9 15.5": ["gol"], "10.7 10.5 9.3": ["exhalations"], "13.7 9.8 14.2": ["swash"], "3.5 10.9 10.8": ["wetback"], "-4.0 12.2 8.8": ["lipase"], "-2.5 -1.2 1.0": ["kindergarden"], "-1.5 9.9 -1.1": ["genotoxic"], "11.9 6.9 7.0": ["snowcapped"], "14.2 4.3 3.9": ["firstquarter"], "10.1 2.8 6.1": ["tomar"], "4.7 4.9 0.9": ["noch"], "7.2 -3.5 2.4": ["woul"], "1.1 0.6 3.6": ["gigajoule"], "26.8 8.3 4.5": ["zillionaire"], "3.6 21.2 22.0": ["scud"], "12.6 16.6 32.4": ["bergs"], "6.7 1.5 28.4": ["fishway"], "0.4 17.0 13.9": ["germinates"], "1.9 3.0 22.1": ["gamy"], "2.7 7.8 -0.1": ["epa"], "4.9 15.1 8.6": ["complexly"], "2.7 5.2 7.8": ["impellers"], "7.7 10.1 6.1": ["walkies"], "5.3 11.1 10.8": ["craftmanship"], "8.6 5.0 11.4": ["competish"], "15.1 13.7 17.0": ["bubbler"], "0.4 12.6 15.8": ["bushed"], "6.4 4.9 15.5": ["proprieties"], "5.4 3.4 1.1": ["nw"], "9.6 4.9 5.8": ["tokenistic"], "7.1 15.2 4.0": ["gainfully"], "8.8 12.5 5.1": ["laminar"], "8.4 11.5 14.1": ["tard"], "29.4 13.0 8.0": ["doodad"], "9.1 5.7 22.3": ["arks"], "0.6 3.8 9.1": ["hectors"], "-3.5 9.8 4.2": ["relators"], "0.6 3.4 10.8": ["dupattas"], "6.4 11.7 9.2": ["allaboutcricket"], "-1.7 5.5 50.2": ["hilsa"], "2.3 1.3 -1.9": ["auspice"], "2.6 13.0 -4.1": ["outsprint"], "8.7 8.9 16.2": ["ewww"], "-0.7 14.4 14.1": ["gruffness"], "-3.0 2.0 -1.9": ["upgradability"], "2.4 14.8 3.7": ["didnot"], "2.6 15.3 13.0": ["maras"], "5.8 8.9 6.5": ["exurb"], "0.7 -0.2 7.3": ["nativities"], "7.0 1.3 0.5": ["cheminformatics"], "-4.0 8.0 7.5": ["ultramarathons"], "25.9 9.9 21.2": ["cruncher"], "-5.6 1.4 2.3": ["ranolazine"], "-0.4 3.9 9.1": ["soundbar"], "1.3 1.4 5.3": ["crowdfunding"], "3.0 12.1 9.5": ["belaboring"], "13.2 8.1 12.3": ["spiritless"], "8.6 9.4 14.4": ["fioricet"], "12.1 4.3 22.5": ["glassblower"], "8.3 0.2 19.5": ["peaky"], "3.8 5.5 11.1": ["assuages"], "8.1 -6.9 1.3": ["furn"], "3.0 8.7 22.3": ["heartiness"], "4.6 -0.6 17.7": ["tou"], "9.2 0.5 8.4": ["hola"], "12.3 17.6 11.9": ["numbskulls"], "4.2 8.2 5.3": ["twiddled"], "5.8 -4.8 13.1": ["silversmithing"], "-2.3 9.8 8.1": ["barrooms"], "3.6 14.0 12.8": ["federo"], "4.2 15.2 11.4": ["hosepipes"], "9.8 0.5 33.1": ["tostada"], "11.4 7.7 16.2": ["stollen"], "-0.9 4.9 -5.5": ["carrer"], "9.2 3.2 13.7": ["tro"], "7.7 16.0 23.9": ["rosebush"], "7.8 6.6 16.8": ["coachman"], "17.6 8.7 7.1": ["wanking"], "7.8 7.5 7.9": ["penstock"], "0.4 11.8 2.9": ["sqaud"], "-3.1 9.6 -7.0": ["reappraising"], "5.2 3.4 18.3": ["potlines"], "11.0 15.6 7.7": ["monolithically"], "6.4 6.9 2.9": ["misspells"], "9.0 1.8 13.6": ["preassembled"], "3.3 9.8 14.5": ["arpeggio"], "-3.3 10.3 -3.6": ["transmittance"], "-6.3 17.5 14.3": ["comebackers"], "-8.2 2.9 1.9": ["homeschools"], "6.4 1.8 5.1": ["unfashionably"], "2.9 10.6 8.9": ["valopicitabine"], "18.7 9.4 28.8": ["swede"], "-2.4 5.5 0.1": ["surcharging"], "-0.3 8.8 18.1": ["onsen"], "26.2 -3.3 4.3": ["countersues"], "-2.9 -0.3 6.3": ["embroiderers"], "2.0 0.9 3.6": ["pharmacologists"], "2.5 18.1 9.0": ["airtankers"], "14.9 20.0 3.9": ["sinisterly"], "11.8 7.7 12.1": ["morris"], "6.4 12.2 10.7": ["fie"], "10.0 27.2 14.2": ["forechecker"], "0.0 4.6 0.3": ["delever"], "16.5 -4.3 1.8": ["spruiked"], "0.2 -3.0 36.6": ["burrata"], "4.7 2.9 22.5": ["boatbuilder"], "6.0 12.3 7.4": ["xyz"], "4.7 17.3 8.9": ["tautological"], "5.3 12.2 2.4": ["haemorrhages"], "7.4 6.5 2.6": ["skiier"], "-2.6 17.8 9.7": ["pleura"], "23.2 7.9 0.4": ["whirs"], "17.2 7.4 16.1": ["tapirs"], "5.4 15.8 15.2": ["fallin"], "12.4 7.2 9.1": ["supercentres"], "-10.4 0.3 2.4": ["levothyroxine"], "-4.4 9.4 5.4": ["extraversion"], "14.1 2.1 7.1": ["woodworks"], "6.3 8.3 8.3": ["bedrolls"], "-0.7 20.8 3.9": ["triggermen"], "-0.5 7.9 10.5": ["douchey"], "-3.1 14.7 4.7": ["itemizes"], "-3.1 3.4 5.9": ["revaccinated"], "0.3 3.2 -1.0": ["compositor"], "20.4 -2.0 17.6": ["specked"], "1.7 14.3 8.5": ["bolters"], "-1.1 9.7 13.4": ["servlet"], "18.8 6.9 26.9": ["capybara"], "0.4 46.2 7.7": ["squadmates"], "9.0 6.8 23.3": ["rosebud"], "-4.6 7.8 -4.1": ["writting"], "0.5 13.8 5.1": ["lopinavir"], "3.7 30.6 16.1": ["swordsmanship"], "5.6 -0.9 9.9": ["neu"], "4.7 5.5 5.8": ["projectionists"], "-2.6 12.2 6.4": ["irradiance"], "4.4 7.4 20.9": ["fluked"], "20.0 4.3 9.5": ["burbled"], "11.1 16.4 0.9": ["farflung"], "1.5 6.8 -0.7": ["wass"], "4.5 7.2 7.4": ["soaping"], "14.2 3.5 10.5": ["shoppe"], "12.7 14.8 2.5": ["battlelines"], "7.6 4.6 3.5": ["gearless"], "5.1 7.5 12.9": ["meri"], "-7.1 7.1 9.2": ["homilist"], "19.3 12.9 19.5": ["muscly"], "9.0 5.5 10.4": ["riffled"], "6.8 1.3 7.7": ["dobbed"], "3.6 11.3 6.0": ["jerkiness"], "7.0 10.7 8.2": ["definetely"], "1.5 3.6 15.6": ["potline"], "-1.7 9.9 17.9": ["unflavored"], "5.4 8.1 26.6": ["idlis"], "28.1 12.4 4.0": ["reorganises"], "5.9 4.2 13.7": ["twangs"], "-2.8 22.2 8.7": ["pathfinding"], "0.7 -1.9 3.6": ["platesetters"], "-4.8 0.9 5.3": ["constructability"], "10.9 2.1 18.5": ["tuckshop"], "-0.3 1.1 10.5": ["hypothalamic"], "9.3 9.5 17.5": ["hibernated"], "6.3 3.5 10.5": ["sketchier"], "1.3 7.4 4.1": ["commiserates"], "9.2 4.9 -0.8": ["savviness"], "17.6 7.1 -1.3": ["dampeners"], "6.5 8.2 4.5": ["infeed"], "13.0 13.9 4.2": ["electromagnetics"], "-2.4 6.0 5.7": ["reallocates"], "-3.4 24.3 7.0": ["misspeaking"], "5.6 11.4 16.6": ["clicky"], "-3.5 8.0 15.9": ["storminess"], "-6.3 19.0 1.4": ["deen"], "17.5 8.6 21.4": ["paddlewheel"], "11.0 8.9 9.9": ["wadding"], "-0.9 5.7 9.5": ["downcycle"], "1.4 6.1 6.0": ["miking"], "2.9 -6.6 6.0": ["boh"], "11.0 13.4 8.0": ["gimbal"], "1.9 13.3 8.0": ["governmentally"], "-10.4 2.8 2.6": ["gasolines"], "10.2 4.4 7.5": ["motavizumab"], "3.0 5.0 10.7": ["wilayats"], "12.9 12.7 10.7": ["thumpin"], "3.5 3.9 10.4": ["prespecified"], "11.2 -4.2 9.5": ["lcd"], "-6.3 -4.1 3.7": ["readdressed"], "12.7 4.7 8.2": ["lightbox"], "-2.4 9.9 0.1": ["relitigate"], "-1.2 -4.6 3.4": ["valleywide"], "12.4 6.0 16.7": ["esky"], "7.8 3.0 3.9": ["bookmobiles"], "20.1 12.2 10.3": ["moodily"], "9.3 7.3 3.7": ["glucometer"], "4.3 4.2 6.9": ["perindopril"], "14.3 10.9 8.8": ["starlit"], "4.8 9.4 6.3": ["muckrakers"], "3.7 6.4 9.1": ["perplexingly"], "5.5 -2.4 6.9": ["noteable"], "1.7 8.1 0.7": ["papped"], "2.3 9.8 39.5": ["rapini"], "-2.7 9.4 6.1": ["ketosis"], "12.2 6.0 8.2": ["unsual"], "-2.4 14.1 11.5": ["suitemates"], "12.2 6.7 20.5": ["sarsaparilla"], "9.0 18.7 7.9": ["rentier"], "0.3 23.1 2.6": ["assaulter"], "-1.8 -0.7 12.8": ["niyang"], "-1.2 0.8 9.2": ["blonder"], "6.5 19.3 3.1": ["consoler"], "2.0 8.1 15.6": ["basta"], "11.9 11.4 13.3": ["neurotics"], "-0.5 14.7 4.7": ["psychoanalyze"], "2.1 0.6 18.7": ["citrine"], "9.3 13.6 10.1": ["plagiarists"], "-6.7 18.2 1.5": ["likelyhood"], "2.0 11.5 13.9": ["lysozyme"], "4.8 14.2 4.3": ["capitulations"], "18.1 7.1 17.5": ["lops"], "9.6 4.9 7.8": ["hol"], "7.9 1.6 3.2": ["reattribution"], "2.8 7.7 0.4": ["beween"], "13.4 7.7 17.4": ["sluicing"], "0.6 5.6 0.1": ["hagiographic"], "4.3 12.3 17.5": ["mara"], "7.9 7.3 17.7": ["nectars"], "4.4 3.9 2.5": ["aut"], "10.6 0.5 13.3": ["iis"], "-8.8 8.3 10.8": ["lactase"], "4.6 2.8 0.1": ["curia"], "4.3 9.0 10.8": ["misfolded"], "-1.3 10.2 4.3": ["synthroid"], "8.9 9.9 44.7": ["butterflied"], "0.1 2.8 19.4": ["scats"], "-1.7 0.6 11.6": ["woolens"], "-1.5 11.9 10.0": ["macroprudential"], "3.3 12.8 6.2": ["fundaments"], "3.1 8.1 9.9": ["gpg"], "14.3 10.5 19.7": ["icebound"], "-0.3 5.9 12.7": ["bioassay"], "15.9 2.4 7.6": ["bulkiness"], "16.5 1.2 18.1": ["lacey"], "3.0 8.3 9.7": ["rooney"], "5.1 15.2 7.1": ["ripostes"], "1.0 16.4 7.2": ["birtherism"], "4.3 8.5 2.0": ["actualised"], "3.9 11.2 12.1": ["algos"], "-1.2 9.2 9.7": ["iteratively"], "7.3 1.5 11.5": ["bookbinder"], "6.1 31.3 7.3": ["nonnuclear"], "12.5 12.4 19.6": ["parfaits"], "9.3 7.3 3.5": ["allready"], "8.5 23.2 11.0": ["blockhouse"], "-5.6 12.9 7.8": ["bruxism"], "1.6 3.8 12.4": ["honeymooner"], "6.4 1.5 1.4": ["waterbeds"], "-2.0 6.0 10.3": ["dua"], "10.8 21.6 8.9": ["apache"], "18.6 -6.1 11.2": ["ahhed"], "11.5 15.3 8.1": ["anally"], "-4.1 8.6 19.7": ["brassica"], "1.1 12.5 10.7": ["hoga"], "1.5 5.4 15.0": ["herpesvirus"], "-7.8 10.7 -0.2": ["imputations"], "4.2 -0.0 12.8": ["hiccuping"], "1.6 6.0 11.8": ["postering"], "-0.5 4.9 -6.0": ["suppport"], "8.1 17.9 -0.1": ["supress"], "10.3 5.2 16.7": ["chinaware"], "5.2 33.4 -0.5": ["putschists"], "9.2 3.1 13.8": ["clinked"], "3.0 4.1 7.6": ["goldfield"], "12.8 3.8 32.9": ["slivered"], "2.9 17.0 3.8": ["baselessly"], "14.7 10.4 6.5": ["busied"], "3.8 1.9 3.2": ["kennedy"], "11.4 7.5 27.8": ["tui"], "-2.2 4.2 9.6": ["uninvested"], "-14.0 11.5 1.6": ["yeshivot"], "0.1 6.9 9.9": ["misfolding"], "5.4 4.8 -1.6": ["comission"], "3.6 5.2 6.2": ["versioned"], "-5.5 6.3 14.3": ["hundi"], "1.9 7.2 22.1": ["wineglasses"], "-10.0 9.3 1.1": ["imput"], "25.9 23.1 15.7": ["cyclops"], "9.4 1.8 11.5": ["bindis"], "10.8 6.3 11.2": ["chesty"], "-6.0 12.9 9.8": ["uppishly"], "-1.9 19.3 11.8": ["vindictively"], "13.6 9.1 7.1": ["supercycle"], "7.4 19.0 13.6": ["radome"], "1.7 8.7 9.4": ["jugalbandi"], "0.5 13.3 12.6": ["parricide"], "15.0 12.9 23.0": ["protuberance"], "12.9 8.5 5.6": ["palindrome"], "11.3 -0.2 10.5": ["washboards"], "10.0 5.5 3.3": ["bracketologists"], "-3.9 2.0 4.8": ["contestability"], "12.4 1.3 16.8": ["veneered"], "1.8 7.3 14.5": ["demotic"], "-4.8 5.3 2.3": ["xylose"], "-4.3 2.4 7.8": ["househunters"], "-0.3 4.1 4.1": ["outraising"], "-4.6 8.0 9.2": ["reapportioned"], "14.4 5.4 10.3": ["ciggie"], "-5.9 -1.4 9.7": ["lyophilized"], "-5.9 19.0 8.2": ["bhakti"], "2.5 10.4 8.5": ["telugu"], "8.7 17.0 6.9": ["vegetate"], "16.4 6.3 10.2": ["tackiest"], "5.4 -0.5 5.7": ["unallowable"], "3.9 17.1 5.8": ["factionalized"], "-2.7 2.2 17.1": ["unshipped"], "9.6 14.2 11.3": ["lipitor"], "7.4 14.7 46.2": ["garfish"], "1.6 11.1 9.9": ["hostname"], "13.6 12.8 13.2": ["ruinously"], "-4.7 3.8 11.2": ["anakinra"], "-0.4 10.3 19.7": ["silat"], "-7.8 13.3 6.9": ["openhearted"], "0.6 13.6 8.6": ["matchpoint"], "9.9 10.0 13.3": ["indexers"], "-1.5 2.2 1.3": ["rls"], "19.1 5.3 30.9": ["middens"], "-1.3 3.0 23.1": ["tankini"], "-0.4 17.9 10.1": ["abominably"], "-6.5 11.8 2.9": ["diffrent"], "6.9 28.6 3.2": ["refight"], "7.2 9.8 6.4": ["hared"], "12.1 11.1 29.8": ["cichlids"], "0.5 4.6 3.0": ["unmedicated"], "-0.8 6.1 3.5": ["lodgment"], "9.2 8.2 32.9": ["tatties"], "7.7 24.4 4.3": ["jailors"], "0.0 5.1 10.1": ["wakeboarder"], "22.1 1.9 5.5": ["coalminer"], "6.4 4.0 4.1": ["doffs"], "4.7 11.2 12.3": ["laserdisc"], "-1.4 7.4 16.8": ["nucleosome"], "2.9 7.8 13.7": ["lungi"], "8.8 7.6 5.3": ["fizzer"], "7.1 8.3 11.8": ["nonunionized"], "10.6 3.7 6.2": ["synfuels"], "2.4 5.9 4.8": ["rallycross"], "4.8 4.9 41.4": ["andouille"], "7.6 7.3 26.8": ["alliums"], "7.7 11.1 22.2": ["flycatcher"], "-0.6 3.4 5.7": ["alitretinoin"], "12.6 10.5 7.9": ["undecipherable"], "9.1 5.1 14.0": ["liquefies"], "3.8 6.8 9.2": ["valvetrain"], "1.8 9.3 12.2": ["laundress"], "-4.1 20.8 8.4": ["checkdown"], "19.6 17.5 20.2": ["smurf"], "-8.1 22.8 1.6": ["dissensions"], "3.4 19.0 11.8": ["escapability"], "-1.7 14.0 16.6": ["singlehood"], "0.3 4.1 13.1": ["lancet"], "-1.6 2.1 13.5": ["toplining"], "4.8 5.1 6.6": ["mso"], "3.4 8.0 14.7": ["bedsore"], "5.2 15.2 0.1": ["unfound"], "11.5 14.9 7.5": ["signification"], "0.5 10.8 4.9": ["intefadeh"], "2.8 19.1 15.1": ["pungently"], "20.3 15.6 23.4": ["slushie"], "12.1 11.7 13.9": ["minheight"], "-6.7 6.6 -1.0": ["neurotransmission"], "-9.6 -1.9 4.2": ["steatosis"], "-0.4 7.4 5.7": ["anion"], "6.1 20.0 7.9": ["ludicrousness"], "5.3 -2.4 9.6": ["sandlots"], "1.1 9.1 23.8": ["icings"], "11.2 4.0 26.7": ["boners"], "5.9 5.6 3.1": ["collison"], "9.3 4.9 16.9": ["rollerbladers"], "2.5 8.2 2.4": ["oportunity"], "1.0 12.2 2.5": ["undemonstrative"], "4.6 28.4 0.9": ["witting"], "-3.7 8.2 9.0": ["crs"], "4.5 11.3 4.1": ["hierarchically"], "-7.8 7.5 31.6": ["mainstem"], "12.2 9.0 0.3": ["barnstormer"], "-14.2 0.8 6.8": ["exceedances"], "-3.1 20.6 -1.6": ["indictee"], "5.6 22.6 11.2": ["sovereignties"], "1.5 0.4 7.4": ["jessica"], "-5.2 4.7 5.8": ["articular"], "-4.9 4.3 10.5": ["leukocyte"], "5.1 4.0 5.3": ["bipartite"], "-1.9 6.7 2.0": ["readback"], "1.6 15.1 8.8": ["otherworldliness"], "11.8 8.7 15.4": ["greasers"], "3.8 4.7 25.3": ["chianti"], "5.8 3.4 20.7": ["speedos"], "6.1 5.8 31.9": ["paratha"], "8.4 5.6 12.9": ["dandiya"], "5.1 16.1 -3.4": ["allways"], "4.5 14.2 -1.4": ["righ"], "-6.1 4.8 1.6": ["ipsilateral"], "-1.8 7.5 -2.9": ["responsibilites"], "-3.9 0.3 0.1": ["abciximab"], "14.1 12.0 6.1": ["autobahns"], "2.4 33.4 0.5": ["jihads"], "-8.7 11.4 8.0": ["neuropathies"], "17.7 6.7 19.3": ["pompons"], "5.0 -0.1 6.7": ["kent"], "5.3 6.5 11.4": ["mf"], "3.5 7.7 -0.7": ["intersegment"], "12.1 -0.5 8.9": ["newsboy"], "4.7 12.0 5.8": ["subsumes"], "7.8 11.6 15.8": ["tink"], "12.4 2.3 20.8": ["polychrome"], "5.2 7.7 9.5": ["cheapies"], "3.7 2.3 19.9": ["linda"], "11.7 12.3 20.3": ["lobed"], "12.1 16.0 12.2": ["strikebreakers"], "10.7 16.3 -6.4": ["emanation"], "0.9 6.6 7.6": ["shriller"], "1.5 8.6 14.9": ["zoonoses"], "17.2 19.1 9.6": ["musketeer"], "12.2 14.4 30.9": ["cockerels"], "-12.3 6.6 0.4": ["cowriter"], "9.2 3.1 12.6": ["boilermakers"], "-9.9 17.4 9.7": ["reinfection"], "11.8 9.1 17.7": ["bullrings"], "3.8 13.6 11.5": ["slipstreaming"], "-7.4 3.3 5.6": ["febuxostat"], "4.5 4.7 3.2": ["kajeet"], "-4.2 14.8 15.3": ["overclocker"], "2.0 1.5 46.2": ["hamachi"], "4.7 5.5 52.6": ["scup"], "4.1 3.4 15.0": ["gg"], "5.4 12.8 7.2": ["threated"], "3.1 -1.8 2.7": ["ime"], "-2.6 7.6 11.4": ["microbiota"], "4.9 4.6 19.1": ["desalinated"], "12.7 18.3 16.4": ["pupate"], "-2.4 3.7 9.5": ["oneday"], "6.5 0.7 19.5": ["marie"], "5.6 29.0 -1.4": ["holocausts"], "9.2 3.7 7.2": ["boyishly"], "6.8 14.8 31.4": ["purslane"], "-10.9 12.2 7.5": ["contemplations"], "0.6 -7.8 1.6": ["ond"], "3.1 10.9 5.5": ["pocketknives"], "7.9 8.3 4.9": ["deconstructionist"], "-3.2 21.1 3.8": ["indubitable"], "-0.4 6.6 13.1": ["midcard"], "7.6 8.0 9.4": ["braless"], "-4.8 11.5 0.8": ["interoperation"], "3.2 24.1 10.8": ["epigram"], "-1.4 10.5 5.5": ["fbs"], "6.8 5.5 25.4": ["gastronomes"], "3.3 5.1 9.0": ["microfabrication"], "10.4 5.8 12.4": ["cept"], "-2.8 3.1 16.3": ["mortise"], "-2.0 10.4 2.0": ["phenomenological"], "3.2 12.9 8.6": ["thrashy"], "10.8 9.3 31.4": ["huitlacoche"], "3.1 8.4 8.3": ["hexadecimal"], "8.8 13.9 14.3": ["hatless"], "12.6 16.7 12.3": ["ineffably"], "4.3 8.2 2.1": ["haberdasher"], "9.9 6.5 20.5": ["twiggy"], "7.3 1.3 6.7": ["customizers"], "-0.3 -0.9 14.8": ["monogramming"], "-3.3 8.6 -2.2": ["tranfer"], "-0.6 9.8 12.5": ["anodizing"], "6.9 8.9 7.8": ["muezzins"], "7.1 12.1 11.6": ["linden"], "14.5 30.2 7.9": ["jinn"], "36.7 2.9 9.7": ["tiddler"], "9.9 8.3 17.4": ["gits"], "-4.5 7.0 2.6": ["debateable"], "2.3 6.9 30.8": ["arecanut"], "-1.8 11.1 3.4": ["rhetorics"], "2.8 13.0 10.5": ["educrats"], "17.7 9.9 1.1": ["megatrend"], "0.3 11.3 16.8": ["minesite"], "9.0 13.9 -2.5": ["unbefitting"], "-0.1 9.1 -0.4": ["overmedicating"], "-11.0 1.1 1.6": ["anthologized"], "7.8 3.1 27.6": ["caber"], "-0.7 14.2 1.2": ["contrarily"], "4.1 20.2 3.5": ["refract"], "-4.6 4.5 4.5": ["ketoconazole"], "2.2 -0.8 17.7": ["pelletizing"], "4.3 8.3 13.9": ["inundations"], "-3.9 -0.8 2.9": ["mehr"], "5.3 2.5 9.7": ["impaction"], "28.5 4.7 14.6": ["meisters"], "26.6 3.5 3.2": ["isation"], "-0.3 9.8 16.7": ["fxgai"], "2.8 18.5 6.6": ["ailerons"], "1.7 -1.1 2.6": ["housebuyers"], "1.1 9.6 -1.6": ["photoluminescent"], "4.0 19.7 11.6": ["submenus"], "-4.4 6.7 10.2": ["syenite"], "14.5 14.8 13.2": ["rathole"], "5.8 15.5 11.6": ["sideswipes"], "11.4 13.2 19.2": ["girdling"], "-5.5 18.3 6.7": ["tortfeasor"], "2.3 14.7 6.9": ["worsts"], "9.5 5.9 11.8": ["vampish"], "9.9 10.2 7.5": ["viewfinders"], "2.5 8.0 14.1": ["pasteurize"], "-0.0 0.1 10.1": ["flashings"], "3.6 1.1 7.6": ["semirural"], "0.1 10.7 33.9": ["electrofishing"], "12.4 11.8 10.6": ["replicator"], "9.1 5.0 20.1": ["froufrou"], "3.8 7.4 21.5": ["pottage"], "-2.4 1.0 -3.2": ["resecuritization"], "1.7 3.5 4.2": ["classiness"], "13.2 4.5 51.3": ["surimi"], "-1.1 7.1 8.9": ["aileron"], "12.2 9.9 7.1": ["skeevy"], "7.5 10.5 6.0": ["masturbates"], "3.2 -6.9 -0.1": ["peform"], "-5.0 5.7 8.6": ["nanomanufacturing"], "10.4 5.1 36.8": ["lumpia"], "16.6 7.0 35.1": ["cisco"], "2.6 4.0 6.1": ["embroiders"], "2.7 5.5 12.4": ["checkoffs"], "3.0 19.0 3.0": ["rightwinger"], "9.2 2.6 23.8": ["pumphouse"], "4.8 -1.6 11.2": ["bellydancing"], "7.5 8.4 9.0": ["cripplingly"], "17.8 6.9 3.5": ["mainlining"], "12.3 5.4 -3.1": ["lauch"], "-4.4 1.6 31.8": ["korma"], "0.2 9.2 10.3": ["verite"], "5.3 -0.0 5.0": ["arte"], "10.8 10.9 35.6": ["cottontail"], "-0.8 3.2 5.3": ["hypoparathyroidism"], "3.5 10.6 16.6": ["tombstoning"], "-1.8 9.4 3.9": ["reclusiveness"], "-2.0 1.7 9.6": ["relaxin"], "1.4 14.2 0.8": ["updip"], "-4.8 3.4 -2.0": ["headways"], "3.4 12.9 16.1": ["mexicans"], "11.3 9.4 31.3": ["potlatch"], "14.9 7.3 29.3": ["hornbills"], "11.3 -0.5 17.1": ["deerskin"], "4.8 -5.6 7.5": ["ora"], "11.3 5.9 7.2": ["streamliner"], "8.9 4.6 9.8": ["halftimes"], "5.1 14.5 -2.7": ["supersensitive"], "-1.7 10.2 8.2": ["porphyries"], "-1.7 3.7 7.9": ["mediclaim"], "14.3 4.5 29.4": ["planked"], "4.3 7.2 9.5": ["tilak"], "11.6 -1.2 7.0": ["wook"], "12.9 7.6 20.7": ["screamin"], "5.6 15.7 -0.3": ["firstround"], "15.9 3.5 4.1": ["poising"], "7.4 7.0 6.1": ["disposability"], "1.1 8.1 9.4": ["denotified"], "7.2 12.3 2.1": ["misnomers"], "-3.1 0.9 13.7": ["siguro"], "3.2 18.1 0.3": ["airlifters"], "-8.7 15.5 5.0": ["conflictive"], "-3.0 10.4 5.5": ["overdriving"], "-2.7 -0.7 -2.6": ["contractility"], "-0.4 2.3 9.5": ["katha"], "5.0 14.4 16.0": ["westernization"], "4.0 2.2 14.7": ["lulu"], "6.3 4.0 15.7": ["rasps"], "12.1 2.2 17.8": ["bioprospecting"], "10.5 14.9 3.5": ["monocular"], "15.6 6.6 6.9": ["inorganically"], "14.6 15.3 -0.6": ["hightailing"], "11.1 14.1 14.5": ["korea"], "16.3 -3.7 14.9": ["mercado"], "14.0 2.4 2.3": ["upcycled"], "-1.2 7.0 9.4": ["monoplane"], "6.6 8.4 5.6": ["quicky"], "9.7 12.1 7.7": ["unfriendliness"], "22.8 19.5 7.8": ["trapdoors"], "12.4 2.9 19.3": ["filigreed"], "3.1 1.9 4.2": ["lended"], "15.5 8.7 14.2": ["smileys"], "3.4 3.4 1.5": ["weblink"], "2.9 -2.6 18.2": ["trayless"], "20.4 -2.6 9.6": ["gewgaws"], "7.1 11.9 15.4": ["lurcher"], "9.6 3.2 7.0": ["datacasting"], "7.9 18.0 10.9": ["anaglyph"], "-5.8 4.1 14.6": ["feedyard"], "4.1 6.0 13.5": ["knicks"], "1.9 -0.2 25.1": ["natto"], "-0.9 5.5 1.6": ["arcplan"], "5.8 15.3 19.8": ["phylloxera"], "-11.2 1.6 -2.0": ["vocationally"], "1.8 1.7 0.6": ["ord"], "-12.6 4.6 -0.5": ["supt"], "11.0 8.6 -0.9": ["ululated"], "20.9 8.6 21.2": ["roundish"], "4.9 3.3 15.9": ["hominin"], "8.4 0.7 8.6": ["overleaf"], "4.6 6.3 6.2": ["alpinist"], "8.4 11.3 4.8": ["schmoozer"], "-3.0 1.1 6.6": ["follwed"], "-0.7 4.3 7.0": ["reinjection"], "7.9 10.5 2.0": ["heirarchy"], "15.3 7.3 6.2": ["gaan"], "4.2 6.2 3.5": ["neuropeptide"], "9.0 5.6 4.6": ["brasher"], "0.1 13.3 6.2": ["reenacts"], "4.9 3.5 10.7": ["tk"], "-0.9 16.3 12.8": ["sangfroid"], "10.0 10.3 4.5": ["windpipes"], "12.4 3.7 39.6": ["hagfish"], "-8.9 4.8 7.4": ["generalizability"], "-10.4 9.4 2.0": ["hadiths"], "-0.7 5.7 2.7": ["radiolabeled"], "-8.6 -0.8 2.0": ["decitabine"], "-6.6 5.2 2.0": ["laptime"], "-3.6 14.3 3.3": ["marginality"], "5.8 6.4 14.5": ["siliceous"], "17.0 17.0 8.8": ["glowers"], "10.3 -1.7 10.6": ["href"], "8.9 7.5 21.1": ["mousses"], "1.9 4.3 -0.2": ["garaging"], "14.5 11.0 10.2": ["ragbag"], "-4.6 14.8 6.0": ["anaphylactic"], "15.4 7.6 15.5": ["sequoias"], "9.0 4.6 14.3": ["tut"], "-0.8 12.9 6.5": ["unfollow"], "2.5 8.6 13.5": ["buttonholes"], "10.2 6.2 6.9": ["swamiji"], "4.0 -5.9 -0.0": ["degli"], "8.6 7.9 25.9": ["tavernas"], "0.3 10.4 14.0": ["olfaction"], "0.4 2.3 2.3": ["tachograph"], "9.6 4.5 14.5": ["billabong"], "7.1 5.5 5.9": ["airframer"], "-1.7 8.4 13.0": ["familia"], "5.9 12.2 18.9": ["rockpile"], "8.5 31.6 3.4": ["tormenter"], "2.6 3.0 9.6": ["hanbok"], "4.5 14.7 9.1": ["gona"], "8.3 22.1 24.0": ["weal"], "7.6 16.2 2.0": ["fireballing"], "7.6 8.3 29.2": ["chitlins"], "11.2 8.9 -1.1": ["internalising"], "-1.9 7.4 4.3": ["trackbacks"], "14.7 45.1 9.4": ["emplacements"], "19.1 4.1 24.0": ["pinewood"], "8.9 2.2 13.9": ["toters"], "-5.6 7.3 0.2": ["potentiate"], "15.4 10.3 16.4": ["poopy"], "6.7 11.5 4.7": ["tortuously"], "-1.1 6.6 16.2": ["kampong"], "14.9 7.2 18.5": ["halfpipes"], "1.1 4.6 0.5": ["picoseconds"], "1.4 15.2 8.3": ["cavil"], "-5.6 -2.3 5.3": ["affluents"], "8.5 6.2 5.3": ["macromolecular"], "3.8 5.8 7.0": ["sein"], "2.2 5.4 43.6": ["shellfishermen"], "2.5 8.4 12.0": ["recompete"], "5.0 16.5 15.2": ["darkies"], "6.4 1.5 9.8": ["tailormade"], "2.1 10.2 6.2": ["wht"], "12.1 11.6 2.5": ["heliostats"], "4.5 -3.4 13.5": ["fda"], "-11.7 6.0 19.9": ["semillon"], "5.5 9.1 17.0": ["vinous"], "3.6 2.8 8.5": ["tshirt"], "0.0 5.8 13.5": ["piercer"], "1.2 10.9 13.0": ["politesse"], "-6.2 2.8 1.4": ["effortful"], "15.4 16.1 -1.3": ["resistent"], "9.6 0.9 1.6": ["vil"], "11.0 11.8 10.3": ["bestie"], "5.8 20.1 10.5": ["unbalancing"], "-5.0 9.3 11.5": ["cyclers"], "1.9 1.2 14.2": ["particpants"], "2.1 11.0 39.5": ["mergansers"], "13.1 9.9 5.6": ["pyrotechnical"], "19.5 8.5 32.3": ["trilobites"], "12.5 17.9 20.6": ["hove"], "15.8 17.9 6.4": ["leers"], "-4.3 17.0 8.7": ["bilateralism"], "1.1 10.2 10.1": ["miniaturist"], "-5.8 2.0 -6.9": ["sonographers"], "5.6 11.6 11.8": ["pedants"], "5.2 -3.8 5.0": ["sch"], "8.8 9.5 6.7": ["swadeshi"], "12.0 4.6 21.2": ["bluebell"], "0.6 8.0 6.2": ["enshrinees"], "14.1 7.6 9.1": ["ampersand"], "1.3 -2.6 4.6": ["myfoxatlanta"], "13.6 6.0 5.1": ["lissome"], "-1.4 7.1 8.9": ["cohabited"], "-3.3 3.7 5.8": ["eth"], "15.9 3.2 2.7": ["ipo"], "4.3 2.9 11.7": ["anthony"], "5.2 6.8 14.4": ["elderflower"], "6.2 12.0 12.2": ["ruggers"], "5.2 18.4 21.1": ["ragwort"], "-1.9 22.7 10.1": ["subnational"], "8.7 7.2 5.4": ["adulterating"], "9.6 2.5 30.4": ["griddled"], "17.6 4.8 5.3": ["wunderkinds"], "-0.7 8.6 10.0": ["warmness"], "0.2 0.3 7.2": ["monologist"], "6.2 9.6 9.2": ["oop", "habitues"], "18.5 15.4 18.4": ["sharpies"], "10.9 -0.1 4.2": ["outlaying"], "12.0 7.0 23.4": ["eland"], "0.6 9.8 9.7": ["naturalizing"], "3.7 2.2 30.3": ["nongame"], "23.7 16.6 13.9": ["slowpoke"], "0.7 7.1 5.5": ["compostability"], "19.3 6.2 6.9": ["intergrated"], "14.5 21.3 16.7": ["mofo"], "4.0 13.1 8.0": ["swilstein"], "1.5 -2.3 5.8": ["biowaste"], "15.2 12.8 29.2": ["highball"], "-1.4 6.2 4.0": ["bandmember"], "4.8 13.3 5.1": ["epicentres"], "9.8 9.7 4.1": ["hardwiring"], "-6.3 21.9 -1.5": ["dalam"], "-9.2 3.6 1.8": ["gazetteer"], "1.0 -13.8 8.6": ["loca"], "5.8 5.5 41.6": ["raviolis"], "-3.4 4.8 3.4": ["parishad"], "-0.7 9.1 11.1": ["anglicized"], "-0.4 9.3 4.2": ["optimizers"], "12.5 23.0 3.7": ["disruptors"], "3.9 18.9 19.2": ["ferals"], "3.1 -0.9 16.3": ["lp"], "12.8 20.6 15.4": ["moonbats"], "7.0 6.3 39.7": ["fettuccini"], "11.8 22.1 28.1": ["protozoan"], "7.3 11.1 20.6": ["mutualism"], "6.6 3.7 32.8": ["rambutan"], "-5.2 11.5 3.4": ["ampicillin"], "-5.0 5.4 16.8": ["millets"], "1.1 5.0 -1.0": ["bmobile"], "12.5 17.0 12.2": ["filesharers"], "-1.5 7.0 18.2": ["oc"], "-9.4 6.4 18.4": ["tikanga"], "8.6 5.8 27.0": ["bready"], "7.8 9.9 10.7": ["transubstantiation"], "7.0 6.5 9.1": ["dustman"], "6.9 1.5 10.1": ["stitcher"], "16.3 15.0 7.5": ["overpromising"], "2.1 14.8 3.1": ["overpressure"], "6.4 5.7 25.7": ["clementine"], "2.9 5.8 -3.1": ["neurophysiological"], "-1.7 3.2 4.2": ["overutilization"], "12.5 15.4 7.2": ["connoting"], "3.2 5.1 18.2": ["taproom"], "8.7 15.9 19.1": ["dekes"], "-3.6 1.5 8.0": ["ziprasidone"], "11.8 2.9 7.1": ["horribles"], "5.6 3.0 17.4": ["intaglio"], "13.7 10.3 7.7": ["grok"], "5.6 17.6 8.9": ["wimpish"], "4.3 6.5 12.1": ["instantiation"], "-3.3 15.4 39.1": ["splake"], "3.3 5.0 26.3": ["halwa"], "10.4 13.5 14.3": ["callused"], "5.0 11.4 -10.3": ["desecrations"], "10.7 8.1 22.6": ["dimpling"], "2.6 4.9 6.9": ["valui"], "8.4 11.0 19.9": ["googlies"], "1.7 26.8 12.8": ["counterpuncher"], "-6.2 9.0 1.2": ["correctives"], "3.6 14.1 6.4": ["triply"], "0.2 -2.5 11.2": ["rheology"], "-10.8 15.3 -1.5": ["approvers"], "16.0 14.8 13.6": ["dunny"], "-5.6 11.2 1.7": ["unvetted"], "2.3 6.8 5.5": ["pazopanib"], "18.4 4.1 4.5": ["megamall"], "-1.4 -1.6 -0.6": ["assyst"], "-5.0 18.8 10.2": ["midrash"], "5.7 -0.9 6.4": ["ragpickers"], "18.8 13.2 13.0": ["symbiotically"], "-3.5 5.8 2.4": ["explicated"], "12.3 5.2 -1.1": ["untendered"], "0.7 5.0 -0.7": ["unsatisfactorily"], "16.0 10.6 11.0": ["strobing"], "4.0 1.5 5.0": ["ombud"], "7.9 7.0 18.5": ["scarps"], "2.8 6.8 15.0": ["crankier"], "3.1 8.4 0.8": ["seperating"], "4.4 1.6 11.0": ["sexploitation"], "9.7 5.5 9.2": ["manikins"], "-0.1 5.2 5.4": ["defrauds"], "-0.9 8.4 0.1": ["celsius"], "9.2 24.5 8.1": ["simpleminded"], "7.7 6.7 10.1": ["spidering"], "-8.0 -3.2 9.6": ["dmt"], "-7.0 10.9 1.3": ["interpolate"], "-8.3 4.3 1.6": ["unratified"], "8.8 2.2 12.9": ["chih"], "12.5 6.2 10.0": ["uncosted"], "14.1 8.4 8.5": ["proctologist"], "7.0 10.9 2.3": ["hydrofluorocarbons"], "11.3 2.4 11.8": ["glimmered"], "7.8 11.9 19.3": ["attractors"], "10.5 8.3 17.6": ["lintels"], "12.5 6.5 7.4": ["cashbox"], "10.4 4.5 1.5": ["finaly"], "3.8 10.7 3.0": ["miscontrolled"], "16.2 18.4 15.5": ["gnarliest"], "10.2 7.0 10.9": ["trop"], "17.1 8.4 25.1": ["corncob"], "8.3 12.9 1.6": ["nigerian"], "7.9 11.1 10.1": ["sunbelt"], "-3.2 3.3 11.9": ["airtimes"], "-3.7 6.1 6.1": ["bridleways"], "2.3 21.0 1.4": ["brutalisation"], "-2.1 10.5 12.1": ["rehabilitators"], "7.2 10.1 9.7": ["stepmum"], "-1.5 11.4 1.9": ["cogency"], "7.7 2.7 14.0": ["untrimmed"], "11.7 12.7 7.2": ["monopolisation"], "12.8 15.0 19.8": ["celled"], "-3.6 2.1 22.6": ["bordeaux"], "0.6 15.4 3.8": ["misidentify"], "12.0 13.5 9.9": ["smiths"], "-6.5 1.1 5.5": ["notarize"], "-11.5 8.3 10.5": ["honorifics"], "12.0 12.2 10.8": ["yip"], "3.5 4.2 15.8": ["tonga"], "5.6 23.5 7.7": ["vectored"], "5.7 7.0 2.8": ["sideloading"], "-3.0 -1.0 -3.1": ["discussant"], "-4.7 -3.0 6.9": ["subadvisory"], "10.4 17.5 13.1": ["smarm"], "17.3 10.0 7.7": ["salivates"], "0.6 9.8 6.8": ["deinterlacing"], "-0.3 3.7 11.6": ["whereafter"], "6.2 6.3 10.3": ["breakfasted"], "4.8 4.8 8.9": ["endocannabinoids"], "17.4 -1.0 49.3": ["langoustine"], "15.6 11.1 14.4": ["cnn"], "-7.3 10.9 11.5": ["churched"], "10.0 19.5 1.1": ["outguns"], "1.5 3.4 7.4": ["bookwork"], "6.4 -2.4 0.5": ["comittee"], "5.6 10.6 8.6": ["smoggiest", "abcess"], "16.7 3.8 9.8": ["squatty"], "3.6 -3.6 8.5": ["leary"], "10.6 12.1 7.7": ["furphy"], "-1.7 6.9 7.6": ["videophiles"], "4.8 39.0 8.4": ["shellfire"], "2.4 16.0 2.5": ["overtreated"], "7.7 14.0 9.0": ["antinuclear"], "14.4 3.4 15.4": ["mewing"], "12.6 8.6 9.9": ["woah"], "9.3 16.5 14.4": ["kookiness"], "-5.4 5.7 1.0": ["vitalize"], "15.5 21.5 3.7": ["pasha"], "-3.2 17.8 5.2": ["debility"], "3.9 5.9 -4.1": ["inexistent"], "10.5 12.9 7.4": ["moxy"], "-13.2 14.8 4.8": ["affiant"], "-2.7 16.5 13.9": ["tourmates"], "4.7 2.8 8.0": ["restorable"], "-3.4 8.4 -0.1": ["tipoffs"], "8.6 -4.4 13.7": ["barware"], "5.9 1.9 12.1": ["gyu"], "5.3 11.5 11.6": ["mccain"], "3.5 6.0 13.7": ["dll"], "3.2 15.9 11.9": ["handsomeness"], "15.8 10.1 2.5": ["screengrab"], "14.1 6.4 9.9": ["magna"], "-4.5 -2.5 4.3": ["colocated"], "5.5 -5.1 6.8": ["uring"], "1.7 14.4 13.7": ["sama"], "16.8 13.4 7.8": ["busying"], "4.0 1.0 17.9": ["vanillin"], "-0.7 2.3 5.5": ["chorales"], "2.7 -2.8 7.4": ["pricings"], "12.2 7.2 15.7": ["paintjob"], "6.9 4.9 16.8": ["kei"], "11.4 7.8 34.8": ["pangolin"], "3.4 16.0 12.5": ["harmfully"], "14.3 3.4 5.4": ["thirstiest"], "1.6 6.0 3.0": ["lasciviousness"], "9.1 9.0 3.7": ["transversal"], "-6.5 -0.6 6.6": ["resit"], "7.1 9.1 24.6": ["apiarist"], "6.2 5.5 11.5": ["supe"], "11.4 14.8 10.6": ["bogans"], "10.4 3.9 4.1": ["boldfaced"], "0.7 7.2 4.4": ["dustier"], "21.5 7.4 27.2": ["gloopy"], "13.8 18.5 6.1": ["ecocide"], "12.0 1.5 5.8": ["faffing"], "6.9 -1.9 19.5": ["hou"], "-0.9 8.8 -0.2": ["desorption"], "-7.1 10.3 6.8": ["intercuts"], "-4.8 15.4 -2.0": ["aerodromes"], "7.1 6.5 18.5": ["broadline"], "16.4 5.8 14.9": ["diapered"], "8.6 5.2 11.5": ["compeition"], "1.5 15.9 4.8": ["synergism"], "10.9 5.8 8.6": ["songsters"], "19.7 14.7 16.7": ["sidewinder"], "3.6 25.0 6.9": ["hasbara"], "11.2 10.4 22.9": ["frangipani"], "-0.8 -4.0 5.7": ["stiches"], "0.9 -1.4 16.0": ["aniline"], "7.1 17.5 23.1": ["awl"], "10.5 5.8 -0.5": ["cannisters"], "15.8 2.6 11.2": ["studding"], "3.7 -1.1 2.9": ["vir"], "12.6 7.2 40.3": ["fisherwoman"], "6.4 6.2 3.9": ["midteens"], "-10.0 -9.2 -5.7": ["receieved"], "-6.0 8.3 7.2": ["etiologies"], "16.3 8.4 17.5": ["hank"], "4.0 7.3 1.3": ["consolatory"], "12.4 24.3 32.8": ["landlubber"], "-0.2 5.6 1.6": ["searchability"], "9.8 6.9 10.1": ["luxuriated"], "0.5 14.9 8.0": ["newshound"], "7.0 8.2 4.6": ["ultrasensitive"], "-7.7 9.0 4.6": ["memoirists"], "6.7 36.8 17.5": ["homeworld"], "-5.0 9.0 14.4": ["translocations"], "5.3 7.8 14.8": ["exfoliated"], "-3.8 0.7 13.6": ["refis"], "11.0 7.7 17.3": ["bluebonnet"], "11.2 7.3 16.0": ["moraines"], "2.4 -6.1 -3.9": ["sublicensed"], "6.7 11.0 8.0": ["someting"], "0.5 4.4 17.7": ["coliforms"], "-3.0 9.4 15.9": ["absurdism"], "3.0 6.0 13.5": ["tarped"], "-5.8 12.3 7.1": ["pranayama"], "15.0 11.0 -1.4": ["epitomising"], "11.3 11.5 4.8": ["laughingstocks"], "14.3 17.1 6.8": ["suicidally"], "5.3 4.7 1.8": ["slumdog"], "0.8 8.3 0.5": ["misdiagnosing"], "14.4 10.7 4.5": ["nabobs"], "3.1 6.0 27.8": ["salvors"], "17.6 11.4 11.3": ["entwining"], "3.2 9.5 0.1": ["literates"], "1.2 -7.7 4.1": ["boardmembers"], "6.3 8.3 7.1": ["cosseting"], "7.0 2.5 25.3": ["portioning"], "5.2 5.0 1.0": ["belters"], "-6.0 14.7 6.4": ["volitional"], "-3.1 6.2 -1.2": ["substitutable"], "4.4 6.9 9.2": ["retroviral"], "8.3 7.6 9.5": ["tympani"], "6.8 12.1 8.1": ["nbsp"], "-1.1 12.3 8.2": ["completist"], "6.3 8.7 11.8": ["fetchingly"], "-0.8 14.8 16.6": ["horndog"], "-12.1 1.2 6.0": ["childbirths"], "7.4 10.7 6.1": ["redevelopers"], "12.0 0.2 14.1": ["blingy"], "-8.6 3.6 4.9": ["blacktopping"], "1.5 10.5 -1.8": ["usefull"], "7.6 7.2 15.7": ["indica"], "5.3 21.4 6.7": ["extirpate"], "1.0 5.0 12.7": ["pericardium"], "9.3 15.9 10.6": ["spitters"], "1.7 9.6 12.7": ["heatpipes"], "17.9 12.8 22.1": ["lollypop"], "-6.2 13.0 7.4": ["pastorally"], "6.2 25.4 8.8": ["ineradicable"], "7.4 8.1 26.6": ["burdock"], "-4.9 0.5 3.7": ["antithrombin"], "-6.9 11.0 2.7": ["overdiagnosed"], "16.3 6.0 -1.1": ["redubbed"], "-0.6 2.6 5.5": ["cbm"], "4.1 22.7 -1.9": ["humanising"], "-6.7 13.9 6.6": ["cryosurgery"], "9.2 11.5 14.0": ["misanthropes"], "4.3 6.5 4.6": ["disinhibition"], "22.7 12.6 17.6": ["spiderman"], "3.8 3.9 9.7": ["hors"], "-1.7 7.8 13.6": ["graywater"], "1.9 4.7 18.8": ["blanco"], "12.4 6.0 36.2": ["kumara"], "-6.1 9.8 6.6": ["raag"], "-2.9 8.8 2.6": ["textually"], "13.7 5.8 17.4": ["lassie"], "13.3 7.8 2.3": ["buddying"], "-0.8 24.8 7.7": ["effectually"], "4.6 8.6 15.7": ["pec"], "6.4 0.4 -3.1": ["computerising"], "-0.4 1.6 12.2": ["cadavere"], "12.3 6.4 11.7": ["mezzanines"], "-1.0 8.6 1.5": ["codons"], "4.9 17.4 4.0": ["nigerians"], "-4.9 7.8 9.1": ["bewailed"], "6.9 0.1 7.1": ["wap"], "5.6 17.2 6.1": ["excitons"], "-0.5 -4.0 14.9": ["bilang"], "-3.8 -4.1 3.6": ["peppier"], "1.9 4.9 10.0": ["lahat"], "1.3 7.6 4.5": ["comunity"], "-3.8 12.4 8.9": ["dayroom"], "-2.3 13.4 6.3": ["unarticulated"], "1.5 8.5 4.2": ["transmissive"], "-8.6 5.6 7.7": ["tretinoin"], "-6.1 -3.2 4.7": ["bg"], "10.3 30.2 8.6": ["claymore"], "-4.9 8.8 4.2": ["libor"], "20.6 17.3 17.2": ["fencepost"], "7.2 15.1 12.8": ["craftiest"], "1.7 18.2 4.0": ["conformists"], "21.1 14.1 38.3": ["angelfish"], "-1.1 19.6 8.6": ["autodidact"], "1.9 25.8 3.4": ["deceitfulness"], "2.8 2.5 2.4": ["biocatalysts"], "11.5 11.5 5.0": ["flimsiness"], "11.4 21.5 9.2": ["proletarians"], "5.4 11.3 0.4": ["dosimeter"], "1.3 17.6 7.2": ["polytheistic"], "-6.2 -0.7 7.3": ["worksession"], "-5.7 9.7 8.0": ["roadracing"], "-9.3 8.0 1.8": ["laptimes"], "-6.2 6.1 0.0": ["carvedilol"], "5.4 12.5 5.5": ["jocularly"], "-0.9 12.8 14.0": ["skiable"], "23.0 9.6 23.7": ["spikey"], "7.0 18.4 7.3": ["glorying"], "0.1 1.6 5.5": ["murabaha"], "8.6 17.1 2.7": ["cryptographers"], "12.1 12.0 14.9": ["javelins"], "0.9 18.7 5.9": ["prevarications"], "6.3 9.3 7.0": ["harrumph"], "-2.0 11.8 1.1": ["jatha"], "5.1 12.7 2.6": ["postulation"], "5.5 -1.2 6.3": ["vanload"], "-4.9 6.8 5.5": ["exhaustingly"], "5.4 8.7 22.1": ["beachfronts"], "20.5 6.3 9.0": ["cableco"], "2.4 6.1 6.5": ["stockcar", "asistance"], "7.0 12.6 9.7": ["impetuously"], "24.3 10.5 22.8": ["fatso"], "7.8 6.7 11.3": ["maltese"], "1.7 11.9 6.5": ["orientalist"], "0.3 31.6 2.8": ["dissimulation"], "9.6 5.6 13.4": ["umi"], "13.6 1.3 17.2": ["myoglobin"], "-0.9 4.0 4.8": ["palce"], "5.1 9.0 19.8": ["gladiolas"], "10.2 18.4 5.0": ["augury"], "2.0 9.7 1.9": ["tiresomely"], "-3.8 7.4 2.1": ["quintets"], "-5.9 6.1 3.7": ["numerologist"], "1.8 3.6 12.1": ["centrifugation"], "-1.0 9.0 9.5": ["antialiasing"], "-7.3 8.1 1.4": ["reasonability"], "7.4 -2.2 -3.2": ["denars"], "5.3 -1.9 3.7": ["tcm"], "5.2 5.9 16.8": ["barters"], "0.4 6.6 14.6": ["ovine", "dingwe"], "-0.6 3.7 1.8": ["ath"], "21.4 14.6 4.0": ["quaked"], "-1.1 3.9 22.9": ["minibottles"], "-5.5 9.9 8.3": ["barhopping"], "-5.0 10.1 18.5": ["shoulds"], "4.2 13.9 2.9": ["metier"], "-12.4 3.2 5.6": ["completers"], "11.6 0.6 1.5": ["clunkier"], "3.7 13.9 -1.5": ["villified"], "11.3 6.8 11.4": ["rogers", "somehwere"], "14.5 2.4 3.6": ["futzing"], "-5.7 7.7 15.9": ["overseed"], "13.6 6.0 14.4": ["dcor"], "11.0 7.9 3.7": ["vestibules"], "-0.5 5.4 6.2": ["memorialization"], "5.3 21.8 18.4": ["bindweed"], "14.2 3.4 5.5": ["bended"], "7.0 3.3 13.1": ["scratchcards"], "2.6 6.1 5.8": ["yens"], "25.8 9.8 14.4": ["megalithic"], "-4.2 6.6 -5.9": ["propounding"], "8.1 6.9 8.9": ["paxil"], "-0.3 10.3 12.1": ["coccyx"], "4.4 9.1 11.5": ["bundh"], "11.7 2.1 8.9": ["terabits"], "8.0 0.4 18.7": ["lor"], "7.3 3.4 10.9": ["hoy"], "-16.2 10.0 8.9": ["unexpended"], "-6.8 7.6 -2.4": ["liklihood"], "3.9 34.5 6.5": ["suiciders"], "7.2 8.8 35.8": ["blini"], "14.3 22.1 11.5": ["wolfpack"], "11.1 6.0 28.1": ["stromboli"], "6.8 11.4 3.1": ["diametrically"], "2.7 11.2 5.8": ["inducible"], "-3.9 23.5 5.2": ["calculative"], "4.7 25.9 9.4": ["atrophying"], "29.9 11.8 11.1": ["supermajor"], "2.2 -1.6 6.7": ["wheelset"], "1.0 8.0 15.9": ["silang"], "2.6 14.1 9.8": ["fisc"], "9.6 2.6 17.3": ["paradegoers"], "1.2 10.8 8.4": ["joshed"], "-0.8 6.6 9.9": ["paso"], "27.1 6.6 25.7": ["stegosaurus"], "3.0 7.7 5.3": ["virtualising"], "10.2 3.6 4.9": ["ringback"], "-1.8 6.2 7.6": ["pontifications"], "-1.5 10.6 10.4": ["stromal"], "-4.7 19.0 10.9": ["outwrestled"], "7.7 4.1 7.0": ["colicky"], "11.3 -0.7 8.7": ["bellbottoms"], "7.5 4.7 16.3": ["enchantingly"], "3.9 2.7 6.1": ["accessorising"], "3.1 15.8 10.2": ["exclamatory"], "7.6 10.4 7.1": ["screamingly"], "6.7 -1.3 13.9": ["lic"], "6.1 10.4 7.3": ["sparkplugs"], "4.4 9.5 25.9": ["fudgy"], "-5.8 6.0 9.8": ["arguido"], "-4.1 13.1 13.0": ["aflatoxins"], "-0.3 13.1 5.1": ["overcomplicate"], "-3.2 5.7 3.0": ["tamsulosin"], "15.6 2.2 7.1": ["czarina"], "7.6 -0.4 16.1": ["ciao"], "10.8 19.1 13.2": ["splays"], "1.7 7.4 26.9": ["woodcutting"], "3.7 6.0 5.7": ["innnings"], "-1.5 8.0 8.1": ["miscuing"], "16.1 25.9 17.2": ["scimitar"], "27.7 -1.9 -3.0": ["whizzy"], "-0.0 8.8 7.5": ["hypothesise"], "3.1 2.3 5.4": ["bir"], "5.6 11.5 7.5": ["indissoluble"], "-10.4 9.4 1.8": ["singable"], "-10.3 1.4 13.2": ["trichotillomania"], "1.3 7.7 7.0": ["palifosfamide"], "10.6 10.4 12.7": ["firewater"], "7.2 13.9 18.9": ["adventurously"], "4.3 11.1 10.9": ["effed"], "9.5 13.1 18.1": ["unibrow"], "15.6 5.6 14.3": ["barney"], "9.9 3.1 7.0": ["spermicide"], "-14.8 1.7 4.5": ["dispositional"], "3.0 13.0 0.3": ["samizdat"], "5.2 22.9 1.2": ["godlessness"], "9.0 1.9 3.5": ["droped"], "-2.7 17.6 1.3": ["subchapter"], "2.1 10.0 11.5": ["congeners"], "4.6 10.5 33.5": ["crispiness"], "5.8 7.6 4.5": ["guanine"], "10.1 6.4 13.5": ["matlab"], "-5.5 12.2 1.2": ["intercessions"], "8.3 17.5 11.5": ["fogger"], "4.7 14.7 10.6": ["posterized"], "-1.8 6.3 6.5": ["skiwear"], "1.7 2.0 4.4": ["nalmefene"], "-9.1 -1.4 11.8": ["housesitting"], "-5.3 9.9 8.1": ["proactivity"], "2.8 8.6 7.4": ["humourist"], "3.7 9.5 6.2": ["hea", "luminol"], "4.0 3.7 8.0": ["gazumping"], "8.0 15.7 7.7": ["sombrely"], "2.5 3.0 44.6": ["minkes"], "1.6 8.9 5.0": ["unburdening"], "13.4 16.0 18.3": ["chainmail"], "6.4 5.9 9.3": ["exhange"], "7.1 19.0 4.5": ["taskmasters"], "15.8 14.1 12.8": ["extrude"], "8.3 13.2 3.6": ["toughies"], "7.9 2.5 7.5": ["hile"], "-2.4 0.8 0.4": ["acquaints"], "4.1 10.2 10.4": ["criers"], "7.1 11.3 29.8": ["fireweed"], "-1.6 11.3 10.7": ["prig"], "1.9 14.2 16.7": ["antitoxin"], "1.4 14.9 12.0": ["imposts"], "-1.6 -0.8 2.1": ["learnerships"], "6.5 7.4 22.7": ["bluestem"], "24.1 20.2 19.2": ["bipeds"], "5.9 7.3 20.3": ["daytrippers"], "15.3 3.7 2.9": ["musuem"], "10.3 12.9 16.0": ["carbonized"], "-1.9 -1.0 -3.7": ["reconverted"], "0.8 12.3 14.7": ["thundersnow"], "3.1 12.7 15.3": ["steelers"], "11.6 11.5 10.6": ["granddads"], "7.3 40.6 13.0": ["soldiery"], "6.9 1.0 2.9": ["suchas"], "10.3 4.5 15.5": ["ballcaps"], "2.8 25.3 1.0": ["pakistani"], "3.7 -2.5 10.9": ["vulcanologists"], "9.5 4.7 9.4": ["milf", "econd"], "9.2 15.8 8.8": ["irritably"], "13.6 18.2 21.2": ["fellers"], "-5.6 13.9 7.2": ["uphills"], "2.6 11.8 12.7": ["latinos"], "5.0 14.5 12.5": ["packrat"], "8.1 8.6 11.8": ["reconsolidation"], "4.4 8.8 6.9": ["idk"], "-2.7 -2.7 12.6": ["microplates"], "1.2 12.7 -0.3": ["attemped"], "9.3 1.4 5.1": ["fourthquarter"], "7.5 1.9 11.4": ["cuatro"], "-2.2 7.2 -3.3": ["accussed"], "2.5 2.5 11.5": ["prefunding"], "24.0 13.7 12.7": ["smarties"], "7.8 14.6 15.8": ["safecracking"], "0.2 10.1 11.4": ["exfoliates"], "2.1 15.5 15.6": ["pastoralism"], "0.9 10.1 7.3": ["imdb"], "11.2 12.5 36.3": ["goshawk"], "1.4 5.8 4.7": ["unbuttoning"], "8.9 1.0 -5.2": ["repurposes"], "1.2 5.0 17.9": ["biobanks"], "-5.0 7.4 8.0": ["chrisgraham"], "3.4 15.6 6.2": ["idler"], "-4.4 15.3 3.6": ["proprioception"], "5.5 11.7 2.7": ["presense"], "6.2 20.0 6.1": ["cauterize"], "10.8 10.2 10.7": ["stepladders"], "9.1 13.0 15.2": ["abiotic"], "15.8 -2.4 10.2": ["rollerskating"], "20.3 18.7 20.3": ["echidna"], "17.6 28.4 1.7": ["deafen"], "-1.3 3.1 6.3": ["duplexing"], "10.7 18.4 16.4": ["lyin"], "14.2 12.3 12.2": ["powdering"], "-0.7 -1.0 9.2": ["resurvey"], "-7.1 9.6 2.2": ["unexecuted"], "7.9 17.7 3.7": ["navi"], "7.1 17.4 8.0": ["politick"], "2.3 10.0 10.1": ["icier"], "10.1 7.1 10.9": ["cbs"], "0.1 -3.0 4.6": ["ics"], "-2.4 19.5 4.1": ["moralize"], "3.5 6.1 8.9": ["ofs"], "6.1 9.2 22.7": ["mandoline"], "-18.6 4.4 4.9": ["splenectomy"], "3.1 4.9 13.9": ["dreaminess"], "3.9 0.0 8.5": ["geld"], "3.4 25.9 5.5": ["reproaching"], "4.0 14.7 38.2": ["jerkbait"], "-10.9 10.9 13.0": ["airshed"], "-1.0 28.5 -1.8": ["signaller"], "12.7 9.9 8.7": ["princelings"], "-3.1 10.9 8.7": ["earthing"], "22.1 20.3 16.7": ["scarab"], "1.3 8.5 14.0": ["preindustrial"], "12.4 15.3 5.3": ["thundercloud"], "9.3 12.7 8.2": ["sleights"], "-3.2 1.8 6.6": ["optocoupler"], "10.4 5.6 45.3": ["langoustines"], "2.1 -4.0 9.4": ["intown"], "10.9 11.9 10.9": ["manhandles"], "7.3 7.4 6.4": ["overdeliver"], "4.7 14.2 10.2": ["doltish"], "26.8 20.5 14.9": ["pterodactyls"], "-1.1 4.5 28.8": ["risottos"], "2.6 20.8 11.4": ["slaveholding"], "19.6 4.6 9.5": ["scamps"], "-1.0 7.4 6.5": ["brillant"], "-6.2 3.3 13.5": ["amin"], "-2.9 12.3 8.9": ["thundery"], "5.9 14.7 20.3": ["sward"], "5.0 1.7 7.2": ["bulimics"], "-0.9 33.2 0.3": ["barbarities"], "3.3 14.0 5.3": ["hyphenation"], "8.7 3.2 20.3": ["milker"], "7.3 5.8 3.0": ["goalsneak"], "5.3 14.8 9.8": ["sardar"], "9.0 5.1 4.8": ["jargons"], "6.9 16.5 -1.4": ["nonstrategic"], "4.1 9.3 6.0": ["dazzlers"], "17.7 2.2 -1.9": ["logotype"], "5.3 11.4 8.1": ["isoprene"], "2.2 12.4 12.6": ["limned"], "10.8 8.8 18.4": ["blithering"], "5.2 21.1 7.4": ["multiculturalist"], "10.4 8.8 25.8": ["cloche"], "0.8 8.8 13.1": ["elizabeth"], "4.5 21.5 1.0": ["outmatch"], "12.7 11.3 1.4": ["vaccum"], "14.1 8.9 6.5": ["compliantly"], "7.5 13.0 24.6": ["shipbreaking"], "22.1 3.2 21.7": ["tetra"], "11.7 16.2 1.5": ["trampy"], "8.5 -6.7 -2.8": ["todayannounced"], "8.0 21.6 13.1": ["countenances"], "-3.1 0.0 16.4": ["saucier"], "-7.9 7.3 3.8": ["madaris"], "6.4 18.0 5.4": ["adroitness"], "-6.8 4.1 9.7": ["humbuckers"], "12.8 4.8 3.4": ["tvs"], "3.7 11.8 32.9": ["meze"], "6.1 17.5 8.2": ["mutability"], "17.4 0.7 31.8": ["baleen"], "8.6 2.2 7.6": ["papercuts"], "-2.7 9.9 15.5": ["laddered"], "-1.6 7.6 5.2": ["transduction"], "5.8 26.6 5.9": ["inshallah"], "-1.7 6.8 1.0": ["acutally"], "3.8 15.7 7.8": ["pureness"], "10.7 11.7 18.3": ["frappuccino"], "4.6 6.4 15.4": ["obi"], "15.8 15.2 14.9": ["shanghaied"], "0.3 2.5 16.5": ["bonspiels"], "4.0 9.0 2.2": ["preelection"], "5.3 23.1 12.0": ["shirkers"], "-1.6 7.4 2.2": ["immobilizers"], "-0.8 7.1 6.4": ["alfabet"], "-3.3 9.7 5.3": ["tds"], "3.4 12.4 0.4": ["satirise"], "-9.0 6.6 6.9": ["predetermination"], "5.1 -5.8 1.5": ["bdrm"], "-4.5 7.5 10.5": ["delicadeza"], "4.0 10.9 15.6": ["thermosphere"], "10.0 6.6 22.6": ["clapboards"], "1.6 0.4 -2.2": ["overal"], "6.2 4.6 21.1": ["aquaponics"], "4.7 7.2 8.7": ["surtitles"], "-2.1 8.1 13.8": ["epigrams"], "-1.9 -1.3 5.7": ["recompiled"], "3.9 -1.4 1.3": ["normalises"], "7.1 6.1 5.6": ["fre", "ici"], "4.9 8.4 8.9": ["bottlenecking"], "11.7 18.6 14.7": ["butterfingers"], "-1.5 7.6 -2.7": ["memeber"], "0.5 12.3 10.0": ["aptness"], "7.4 -0.7 13.2": ["nuevo"], "0.7 16.1 0.5": ["desensitizes"], "-5.0 1.5 6.1": ["theophylline"], "8.9 14.2 15.5": ["backlink"], "1.7 4.5 9.6": ["comebacking"], "12.9 4.8 9.2": ["melbourne"], "-3.1 8.8 45.2": ["oystering"], "6.6 9.3 6.9": ["dumbs"], "6.2 12.3 3.3": ["nonbanks"], "15.0 2.2 9.1": ["shirty"], "4.2 2.7 7.3": ["trialware"], "4.0 16.9 9.2": ["professoriate"], "4.4 6.9 24.9": ["plumeria"], "2.7 8.9 2.4": ["hellip"], "1.4 3.8 8.2": ["millisievert"], "-7.6 13.3 4.8": ["davening"], "4.2 0.2 3.3": ["convertors"], "10.2 5.4 18.0": ["yachtswoman"], "2.9 17.9 4.4": ["stans"], "8.2 15.7 7.2": ["shyest"], "-3.4 15.5 7.8": ["threepoint"], "20.8 10.6 8.0": ["tellies"], "1.1 16.5 24.8": ["pronghorns"], "24.9 11.4 23.5": ["phalluses"], "8.9 10.2 8.7": ["drunkest"], "20.4 9.6 36.9": ["narwhals"], "7.1 18.0 0.6": ["fastness"], "-7.1 9.3 7.1": ["catagories"], "0.8 4.4 8.2": ["homebuilt"], "0.7 3.5 7.4": ["duplexer"], "-1.6 3.1 22.5": ["seasonably"], "0.2 16.4 7.8": ["boundries"], "6.9 8.7 21.5": ["pav"], "-6.5 15.0 4.5": ["uncuffed"], "0.4 8.1 8.2": ["ecclesiastic"], "19.8 1.2 22.9": ["fastfood"], "8.4 12.0 9.1": ["protractor"], "-1.0 6.4 9.0": ["discolorations"], "-0.5 12.1 7.3": ["stepmothers"], "-8.3 4.9 11.4": ["annualize"], "15.7 12.2 12.1": ["yippee"], "1.4 14.8 4.8": ["dismissiveness"], "9.8 9.2 13.5": ["rainmaking"], "3.3 4.2 10.1": ["karen"], "20.7 21.3 15.3": ["wolfs"], "14.5 6.8 12.1": ["bruce"], "-5.1 2.2 1.8": ["mitral"], "-11.8 9.8 8.7": ["encored"], "4.0 23.9 5.3": ["strategery"], "-0.3 -1.1 7.6": ["clothings"], "7.4 6.6 5.7": ["snatchings"], "9.3 11.4 10.8": ["skedaddle"], "22.0 12.0 1.2": ["whooshes"], "-4.8 9.4 9.9": ["matrilineal"], "16.4 24.3 14.9": ["dreamworld"], "1.2 2.4 17.1": ["emulsification"], "-2.6 5.0 25.6": ["parathas"], "11.6 5.1 -3.2": ["debitel"], "-2.4 6.0 10.8": ["clarifiers"], "9.3 13.8 15.1": ["mata"], "1.2 0.9 13.3": ["sono"], "11.7 16.9 13.2": ["foolery"], "9.8 -1.2 4.3": ["crystallises"], "-0.1 5.1 -1.8": ["seeked"], "2.3 -0.4 -1.0": ["dapoxetine"], "0.7 5.2 12.4": ["stablise"], "6.5 5.7 6.5": ["graphitic"], "8.0 0.3 9.7": ["egaming"], "0.8 8.0 2.1": ["pedophilic"], "0.8 6.6 6.1": ["stranglings"], "1.2 8.0 -0.1": ["partings"], "1.1 -4.9 6.4": ["oversubscriptions"], "1.6 6.1 57.5": ["quahogs"], "-5.4 10.6 -1.0": ["conceeded"], "-3.9 0.2 1.6": ["docketing"], "10.0 13.2 13.8": ["ritualised"], "6.5 9.8 7.1": ["outboarded"], "4.9 18.6 3.2": ["repaints"], "18.5 6.7 9.8": ["bedazzling"], "7.8 2.8 8.5": ["horseriding"], "-8.9 -0.6 23.5": ["yaqona"], "2.6 0.3 4.4": ["learndirect"], "0.4 2.6 14.2": ["sericite"], "9.1 6.1 18.9": ["scouse"], "-3.5 4.7 18.0": ["overnighters"], "11.5 13.0 4.8": ["cultlike"], "6.1 26.0 0.6": ["dehumanisation"], "-1.7 -0.6 11.0": ["abdominoplasty"], "4.1 13.2 4.6": ["truther"], "12.8 3.2 8.3": ["afros"], "6.4 0.7 13.4": ["beth"], "-3.7 7.1 4.7": ["sidefooting"], "-6.6 0.8 0.0": ["affirmance"], "-4.3 9.8 2.0": ["differentiations"], "3.9 5.6 13.4": ["gulal"], "11.2 1.0 -6.3": ["signifcant"], "1.1 8.1 10.9": ["dachas"], "11.2 6.7 7.7": ["skirl"], "-4.1 5.6 0.5": ["rebanding"], "2.6 15.7 2.0": ["traumatise"], "-1.1 13.2 9.8": ["demagogued"], "1.4 8.2 2.5": ["neuropsychiatry"], "-0.2 -1.4 6.6": ["ppts"], "3.5 3.2 18.1": ["freeport"], "-6.8 2.3 10.2": ["episcopacy"], "5.7 9.4 7.1": ["crossbenchers"], "7.4 4.8 9.7": ["ingenues"], "0.8 1.0 3.9": ["conveyancers"], "-9.0 -3.9 -0.5": ["chapbooks"], "9.8 7.5 13.0": ["castors"], "2.2 13.8 8.7": ["humoring"], "3.8 5.1 9.7": ["laparoscope"], "19.7 9.0 7.9": ["brashest"], "5.2 25.6 17.6": ["histamines"], "-2.5 8.8 11.3": ["deciles"], "10.9 8.0 15.7": ["sooooooo"], "-3.1 14.1 15.0": ["micromanages"], "-1.8 17.2 3.5": ["heterosexism"], "4.3 4.4 8.1": ["eva"], "19.2 10.1 11.3": ["packin"], "0.0 6.1 3.5": ["grammer"], "-0.2 11.8 4.8": ["foxing"], "7.1 3.9 8.7": ["quel"], "15.7 13.5 25.3": ["cerulean"], "11.9 17.8 18.3": ["pappy"], "8.7 15.2 2.5": ["igniters"], "4.2 12.9 2.9": ["innning"], "9.5 4.8 3.3": ["amortising"], "-4.9 -1.1 16.2": ["lehengas"], "2.3 6.0 22.8": ["barbacoa"], "4.6 8.4 20.5": ["pruner"], "4.9 0.6 7.2": ["kerbing"], "-4.5 3.1 9.0": ["prostatic"], "-8.6 3.7 8.3": ["viscosities"], "-2.8 -5.0 1.4": ["mucopolysaccharidosis"], "2.3 8.6 6.4": ["elegies"], "4.4 7.2 3.7": ["didanosine"], "1.3 5.7 8.7": ["unsterilized"], "12.9 8.0 9.4": ["cashpoints"], "2.5 5.2 -0.4": ["pulsatile"], "4.6 10.4 9.9": ["currying"], "-0.1 0.4 19.2": ["ombre"], "5.2 7.8 5.1": ["tranquilisers"], "3.0 12.5 12.5": ["gorier"], "11.4 11.0 12.2": ["serif"], "7.6 10.9 10.5": ["quint"], "-2.0 14.3 8.4": ["wakeful"], "-1.0 9.0 19.1": ["vig"], "6.0 -3.9 15.4": ["mun"], "-3.8 7.4 9.3": ["homeschooler"], "11.6 0.2 25.4": ["hadrosaur"], "-6.6 7.9 15.6": ["turnback"], "1.1 11.3 9.5": ["intracity"], "4.1 11.8 9.1": ["moleskin"], "5.2 5.2 9.1": ["ossification"], "14.5 25.6 5.9": ["outfoxing"], "5.0 14.4 2.3": ["brotherhoods"], "16.9 5.7 8.5": ["spellchecker"], "5.2 5.4 24.3": ["tailrace"], "-0.7 9.0 5.4": ["parchments"], "3.5 2.7 13.0": ["snoozy"], "5.3 2.7 8.6": ["substructures"], "1.4 11.4 5.8": ["motorcyles"], "3.2 28.2 7.9": ["paranoids"], "-5.1 10.5 10.1": ["outgain"], "13.1 25.0 14.8": ["knave"], "8.1 0.1 10.5": ["vitrified"], "12.8 1.3 26.9": ["carne"], "-7.7 12.8 3.4": ["conferral"], "-0.5 3.1 1.9": ["aking"], "15.0 7.2 -1.4": ["racheting"], "9.4 3.6 10.5": ["fripperies"], "7.2 9.5 9.9": ["plebian"], "6.1 10.7 14.2": ["scarp"], "12.7 7.4 14.9": ["pectorals"], "1.9 6.0 10.6": ["bravos"], "-2.3 0.0 -1.8": ["preforming"], "-2.7 7.1 5.7": ["authorizer"], "-12.2 6.2 -0.6": ["hyperkalemia"], "12.9 6.8 11.5": ["jejune"], "13.4 12.9 17.6": ["leathered"], "25.3 3.7 9.0": ["erector"], "12.1 8.2 14.4": ["croupiers"], "7.1 6.6 11.8": ["hei"], "16.5 9.6 20.8": ["sluiced"], "8.2 10.4 9.5": ["tare"], "2.0 21.2 4.1": ["gunrunner"], "2.6 13.3 13.9": ["snowline"], "6.5 8.2 32.4": ["custardy"], "3.0 14.2 51.7": ["longliners"], "16.1 8.5 15.3": ["vancouver"], "0.8 15.4 6.0": ["landlessness"], "3.2 0.3 52.7": ["capelin"], "5.6 7.6 1.4": ["indemnifies"], "25.4 3.9 10.9": ["biggish"], "4.5 6.8 15.2": ["weh"], "17.4 6.0 14.5": ["cyclorama"], "3.5 -2.5 18.7": ["susan"], "6.2 4.2 4.7": ["showreel"], "7.8 -5.3 8.1": ["scissored"], "5.5 6.6 15.6": ["nin"], "-1.3 15.4 8.9": ["delegator"], "0.1 -4.0 0.3": ["follwing"], "11.1 7.4 7.6": ["tweetup"], "-3.5 -0.3 10.8": ["shirting"], "19.4 1.2 19.4": ["sculpturing"], "9.7 21.3 13.8": ["devilment"], "9.1 8.9 13.0": ["postfight"], "4.7 22.0 14.1": ["corruptors"], "1.1 10.1 10.7": ["divisor"], "11.1 -0.6 6.8": ["breakdancer"], "-7.4 -4.8 7.0": ["paroling"], "10.6 -0.1 8.4": ["fragranced"], "-1.6 15.9 10.9": ["incorrigibly"], "2.4 10.7 6.1": ["consummates"], "8.7 1.9 10.7": ["stuccoed"], "11.4 19.6 19.7": ["submersed"], "-0.0 28.5 6.0": ["impious"], "0.0 14.8 4.6": ["multimeter"], "0.7 9.7 4.0": ["diamantaires"], "17.3 8.7 7.9": ["oleaginous"], "0.8 7.7 2.7": ["setpoint"], "-7.2 7.2 8.2": ["formalistic"], "-2.1 13.8 11.3": ["mutagenesis"], "2.5 -2.7 7.1": ["laxer"], "8.4 4.2 17.3": ["glassblowers"], "-5.1 -5.5 -2.7": ["witheld"], "7.7 2.9 10.3": ["ette"], "6.5 8.7 6.8": ["supersaturated"], "2.7 19.1 8.1": ["juntas"], "-1.9 6.9 19.5": ["dischargers"], "2.2 11.1 11.5": ["subfamily"], "14.4 11.5 21.0": ["philodendron"], "12.0 3.8 -2.3": ["dunnhumby"], "4.9 11.2 26.8": ["calcareous"], "8.4 14.4 9.0": ["luvvie"], "2.4 -1.3 16.8": ["hawaii"], "2.0 12.5 5.3": ["yagna"], "-1.5 14.5 4.0": ["sgt"], "-2.6 6.4 13.3": ["immersions"], "14.7 2.7 16.2": ["caribbean"], "4.1 2.0 -4.0": ["accessable"], "-9.3 -0.8 6.7": ["cumecs"], "-10.6 12.3 7.1": ["favorables"], "-4.5 0.1 9.1": ["periodontics"], "-7.6 5.0 -2.9": ["committers"], "-3.1 7.2 6.3": ["mohel"], "-0.8 17.0 -0.0": ["empathising"], "29.4 11.1 22.3": ["beachball"], "5.9 17.7 10.9": ["countrysides"], "14.1 12.7 12.2": ["shepherdess"], "8.3 -0.3 5.1": ["unintimidating"], "3.4 15.4 9.8": ["frailest"], "-4.5 -2.7 8.8": ["toplines"], "2.9 10.7 13.4": ["css"], "25.7 16.4 26.0": ["furball"], "-1.6 2.1 9.5": ["sugarbeets"], "-4.2 2.5 14.6": ["bellydance"], "12.8 31.2 15.8": ["teleporter"], "1.8 11.0 14.0": ["heterochromatin"], "6.1 11.1 19.4": ["pubes"], "13.2 18.3 10.4": ["hobgoblins"], "9.6 0.3 7.1": ["panhandled"], "16.0 1.8 -2.3": ["lucratively"], "11.1 9.9 16.0": ["oke"], "1.5 9.0 8.8": ["locomotor"], "-2.4 1.8 4.0": ["baclofen", "decommitment"], "2.2 -3.5 4.9": ["xkoto"], "-10.2 7.6 10.1": ["humidities"], "18.4 -1.0 0.9": ["techology"], "-3.0 10.2 7.5": ["padyatra"], "0.2 10.3 14.4": ["maa"], "5.6 1.7 27.4": ["gai"], "-0.8 7.6 -1.0": ["mulitple"], "0.4 1.9 18.6": ["kiddush"], "21.3 1.8 19.1": ["sphinxes"], "-2.5 4.8 -1.9": ["financeable"], "2.6 1.6 7.3": ["wir"], "6.3 3.2 8.2": ["expections"], "4.9 7.1 10.3": ["sched"], "11.6 10.7 9.5": ["styluses"], "9.3 4.1 23.5": ["muumuu"], "4.2 5.6 23.3": ["vernal"], "14.9 9.1 35.0": ["nasturtium"], "3.9 -1.9 2.8": ["prequalifying"], "-3.3 -0.6 3.7": ["duringthe"], "7.6 -0.1 0.9": ["witht"], "0.4 -3.2 7.0": ["ractopamine"], "8.2 3.8 39.0": ["collard"], "8.1 10.0 19.7": ["skidder"], "3.8 6.4 39.2": ["lings"], "11.3 16.7 14.3": ["strider"], "0.3 8.1 10.9": ["trendless"], "2.7 15.2 8.1": ["padres"], "9.6 10.9 16.7": ["gelt"], "14.6 0.0 37.0": ["tureen"], "8.2 1.6 12.6": ["nanophotonics"], "8.8 7.9 16.3": ["roid"], "13.5 3.0 4.6": ["marketwide"], "4.9 24.2 13.3": ["cavaliers"], "4.4 10.0 7.9": ["juche"], "6.3 0.6 13.4": ["puro"], "3.1 6.3 32.7": ["galangal"], "13.5 5.9 21.6": ["tsumani"], "1.9 7.4 6.8": ["lindane"], "10.6 -5.6 15.9": ["flatiron"], "5.8 3.7 18.4": ["ikat"], "11.9 14.4 6.2": ["boors"], "-0.2 16.7 9.5": ["sojourners"], "12.0 -7.1 3.3": ["thisyear"], "0.5 3.2 6.6": ["downlights"], "2.8 8.6 2.2": ["farmin"], "10.0 9.2 24.1": ["muskeg"], "18.1 16.7 6.7": ["magnetised"], "5.5 6.5 13.1": ["flexure"], "7.4 6.9 4.7": ["disfunctional"], "2.5 15.7 12.9": ["extirpation"], "2.4 10.8 14.9": ["knick"], "6.9 12.0 -2.2": ["electrochromic"], "15.5 10.6 8.9": ["enfold"], "10.0 7.6 8.6": ["cording"], "2.5 4.8 10.1": ["chanson"], "10.7 10.8 11.3": ["gorefest"], "-0.1 7.7 13.2": ["stopgaps"], "3.6 22.3 11.5": ["ensigns"], "15.9 12.6 10.6": ["plodders"], "1.6 8.3 3.6": ["especialy"], "6.9 1.6 -0.5": ["nitinol"], "12.8 17.0 10.0": ["spaceplane"], "11.6 8.1 6.3": ["keyholes"], "8.4 1.6 17.2": ["extremophiles"], "15.5 10.8 44.5": ["dragger"], "3.2 19.7 8.9": ["irremediable"], "8.1 38.4 3.1": ["gunsights"], "-4.8 1.6 8.8": ["glipizide"], "5.0 13.5 16.8": ["preservers"], "0.7 29.3 5.8": ["dhimmis"], "-11.3 17.3 4.3": ["abridgment"], "13.2 11.0 15.1": ["puckers"], "1.5 0.2 12.9": ["kam"], "1.7 13.2 16.0": ["geomorphology"], "3.8 7.3 21.0": ["piggeries"], "14.3 6.8 6.1": ["centerpoint"], "6.3 12.3 33.4": ["floes"], "-3.5 6.7 6.7": ["synaesthesia"], "13.2 14.9 4.1": ["remolded"], "-9.7 5.9 11.6": ["indigency"], "-4.6 5.8 4.2": ["datango"], "9.1 10.0 12.1": ["endboards"], "2.8 6.1 -1.5": ["haben"], "-4.9 0.7 2.4": ["facilitations"], "18.7 13.9 3.7": ["bajillion"], "5.4 -0.2 3.5": ["registerable"], "6.5 11.6 10.2": ["marooning"], "-1.8 17.0 16.8": ["mudder"], "9.0 6.8 16.7": ["bowlegged"], "-0.6 18.6 5.5": ["gaurd"], "-5.5 8.3 7.5": ["underfunds"], "-6.9 4.4 9.9": ["karatekas"], "7.6 6.6 5.2": ["unwearable"], "18.0 8.3 7.8": ["wildcatters"], "1.1 19.5 1.3": ["guerre"], "6.5 8.0 1.3": ["haved"], "14.5 26.3 21.3": ["swordfight"], "12.0 3.7 5.8": ["chiselling"], "0.1 6.1 4.8": ["interlocal"], "9.3 17.2 13.3": ["numinous"], "-9.0 -7.1 9.2": ["accom"], "13.7 10.3 6.2": ["flipbook"], "0.3 7.3 14.0": ["kwon"], "6.6 7.7 30.7": ["ladyfingers"], "3.8 9.2 15.2": ["pointillism"], "0.6 7.6 14.7": ["coagulant"], "8.9 -1.9 2.4": ["bigg"], "0.8 9.3 13.0": ["kyle"], "-2.1 6.5 11.3": ["preclusion"], "-4.6 2.8 1.3": ["negligibly"], "11.1 14.0 6.3": ["nike"], "11.2 5.4 4.9": ["itwas"], "-8.2 2.0 16.4": ["triplexes"], "1.9 8.5 8.4": ["arrestingly"], "5.7 13.1 10.8": ["husbanding"], "-2.1 2.6 7.8": ["prediabetic"], "11.2 5.2 15.8": ["frump"], "13.3 13.3 17.1": ["icecaps"], "11.7 17.7 25.6": ["twitchers"], "-2.1 -0.1 2.0": ["remasters"], "-10.6 4.4 -3.5": ["consultees"], "-5.5 3.2 0.3": ["tocilizumab"], "12.2 2.9 2.4": ["phonographs"], "2.7 17.2 4.9": ["indefatigably"], "5.0 1.8 12.4": ["vlb"], "13.7 6.9 5.0": ["electrowetting"], "7.8 16.8 5.9": ["heinously"], "10.5 4.6 8.4": ["vaseline"], "-1.4 5.6 25.0": ["kheer"], "-7.9 4.1 4.8": ["darinaparsin"], "36.8 6.3 28.9": ["munchers"], "-1.8 11.6 4.4": ["malversation"], "0.7 12.5 3.3": ["incarnates"], "7.2 1.3 19.3": ["parimutuels"], "-0.4 1.2 -4.8": ["inthinc"], "13.9 12.2 12.0": ["gnomic"], "11.4 9.2 15.2": ["botanic"], "16.7 13.8 24.1": ["blotched"], "12.1 6.9 3.7": ["trig"], "6.2 1.1 3.8": ["fue"], "11.3 6.2 4.6": ["chitchatting"], "-9.3 9.0 -0.3": ["comfortability"], "5.2 2.3 9.9": ["catechumens"], "1.3 2.2 -6.6": ["counterclaimed"], "5.5 7.2 11.4": ["supermodified"], "-6.2 -4.3 4.0": ["dysmenorrhea"], "6.4 -4.1 7.9": ["mewn"], "4.4 7.2 -0.8": ["numberplates"], "17.9 11.7 23.9": ["hippopotamuses"], "9.0 2.5 15.4": ["frolicsome"], "-0.4 8.6 4.3": ["unprosecuted"], "10.2 42.8 11.9": ["reticule"], "2.8 13.3 9.4": ["regularities"], "2.3 0.8 6.9": ["retirment"], "11.5 8.0 6.3": ["blogsphere"], "21.2 0.4 12.0": ["spangles"], "2.2 4.6 0.5": ["mophie"], "-10.7 8.9 7.3": ["selectee"], "3.5 5.0 13.6": ["oligosaccharides"], "11.7 11.2 17.0": ["cals"], "-5.9 14.5 -1.1": ["vitrectomy"], "21.9 19.7 22.0": ["windsock"], "4.5 -0.2 10.9": ["gaelic"], "5.4 27.1 8.8": ["comandante"], "14.7 14.1 17.0": ["headscissors"], "3.7 12.1 5.4": ["deskbound"], "6.2 18.2 21.0": ["barbequing"], "14.6 11.8 10.5": ["reemerges"], "9.3 12.0 13.0": ["macchiato"], "12.5 4.8 52.4": ["pilchard"], "15.9 8.1 6.5": ["illuminati"], "5.6 28.9 3.5": ["islamist"], "9.4 18.2 11.2": ["descriptively"], "-6.9 1.8 -1.9": ["hypocalcemia"], "4.5 24.0 11.7": ["roleplay"], "22.8 21.7 22.0": ["galleons"], "2.9 17.4 1.2": ["newsperson"], "5.9 7.5 8.9": ["tourbillon"], "8.0 19.9 10.5": ["catenaccio"], "-1.8 40.4 7.4": ["insurrectionists"], "11.3 14.9 9.4": ["sociality"], "7.3 1.9 6.7": ["hullaballoo"], "-4.3 -1.3 2.2": ["presscon"], "10.8 14.2 -2.3": ["initializing"], "1.4 9.5 13.0": ["gaiters"], "13.8 -4.9 1.5": ["awardwinning"], "-3.7 8.7 12.9": ["backtesting"], "35.2 33.3 17.9": ["colossi"], "-0.6 9.7 3.8": ["thusfar"], "11.7 4.4 20.8": ["momo"], "14.4 5.4 4.8": ["iomart"], "7.3 6.0 9.7": ["measurer"], "9.6 7.7 32.9": ["hangi"], "12.8 13.2 2.6": ["telemetric"], "21.4 14.3 5.6": ["automata"], "3.4 6.8 7.0": ["bourne"], "13.1 15.9 27.4": ["dinoflagellates"], "9.8 0.9 11.4": ["tiffany"], "-3.3 2.5 -4.0": ["susp"], "-8.2 10.4 2.2": ["recompleted"], "5.9 11.9 6.5": ["jetsetters"], "9.0 4.4 17.1": ["bomba"], "-4.8 19.2 6.8": ["sena"], "12.7 17.5 33.7": ["bulrushes"], "4.7 -0.9 10.1": ["indiana"], "1.5 7.5 13.4": ["unpaired"], "13.0 4.6 8.2": ["speedbump"], "3.0 7.2 7.7": ["twp"], "7.5 8.4 3.9": ["bareness"], "5.6 18.3 13.1": ["hardhearted"], "-3.5 10.1 16.7": ["fallowing"], "7.6 16.1 9.2": ["governmnet"], "4.8 -1.9 5.1": ["caprolactam"], "-2.6 12.7 4.8": ["trenchantly"], "-5.3 4.1 0.0": ["nesiritide"], "18.1 24.9 22.4": ["houseflies"], "13.3 5.2 37.1": ["kippers"], "7.1 3.0 12.4": ["cleveland"], "1.0 6.6 10.1": ["sarpanches"], "2.8 12.9 18.7": ["filariasis"], "18.0 8.1 7.6": ["nationalizes"], "-6.1 10.1 10.8": ["countians"], "4.9 2.1 12.2": ["sterol"], "10.7 30.6 21.6": ["dropship"], "7.7 13.2 10.0": ["plentifully"], "-9.3 0.3 8.1": ["runnersup"], "2.0 6.5 8.5": ["xoxo"], "8.1 5.0 5.8": ["largecap"], "7.5 -4.9 10.4": ["sublets"], "5.3 0.1 5.2": ["undercharging"], "10.0 12.8 21.8": ["gramps"], "-3.8 8.7 -1.8": ["recommendatory"], "7.1 7.5 2.6": ["ionospheric"], "-5.0 8.4 7.5": ["transfected"], "13.0 5.4 10.4": ["conceptualist"], "16.5 21.2 10.7": ["dumbly"], "16.1 6.7 17.6": ["knickknack"], "-5.0 7.1 1.6": ["airberlin"], "2.0 15.2 -6.6": ["linkable"], "6.6 13.9 5.6": ["luminously"], "6.6 8.3 11.3": ["washdown"], "3.9 7.6 7.5": ["matrixes"], "12.9 0.6 19.0": ["dreadlock"], "2.2 12.5 9.3": ["overcommit"], "2.2 25.9 2.4": ["reconquest"], "-3.5 -2.3 8.0": ["nia"], "7.1 8.9 7.0": ["ballasted"], "6.4 7.8 10.2": ["ringbearer"], "7.7 9.7 53.6": ["whelks"], "-0.2 7.4 10.0": ["abbeys"], "-0.5 11.8 14.6": ["glaciated"], "2.4 32.9 12.1": ["chickenhawk"], "-5.6 -1.4 9.8": ["nanogram"], "0.4 19.9 8.2": ["showmance"], "2.8 31.2 12.4": ["incendiaries"], "8.9 14.4 4.9": ["interdivision"], "1.7 2.8 11.3": ["sassiness"], "19.0 22.2 17.1": ["splats"], "9.8 -7.2 8.6": ["assoc"], "15.5 16.4 12.5": ["schmo"], "-3.9 4.6 2.4": ["triptan"], "8.4 1.2 10.6": ["unstressed"], "4.6 -0.1 12.4": ["iyong"], "7.6 2.5 10.0": ["classicists"], "14.0 10.3 5.2": ["mineworker"], "0.1 17.2 8.5": ["misjudges"], "8.6 4.3 3.8": ["featued"], "5.6 -7.0 5.0": ["cher"], "2.1 9.4 4.6": ["sneezers"], "-2.1 9.5 13.6": ["rocksteady"], "-2.4 4.5 14.5": ["sanitarians"], "7.8 -0.6 -2.5": ["informercial"], "8.6 12.6 22.6": ["lucking"], "15.9 -4.5 -0.4": ["heeft"], "5.6 21.5 3.9": ["contagions"], "3.5 13.2 8.1": ["peope"], "14.4 9.5 15.5": ["cumulus"], "6.4 8.3 9.9": ["immigratio"], "7.2 18.1 11.5": ["bigheaded"], "14.4 5.5 5.3": ["storeman"], "-5.4 14.8 0.2": ["experientially"], "2.7 -2.4 2.1": ["multidiscipline"], "6.6 2.8 0.5": ["roflumilast"], "-2.4 10.5 8.1": ["rythm", "iof"], "-0.2 19.6 9.7": ["aspersion"], "0.1 3.8 12.6": ["selectorial"], "-5.7 -1.7 6.5": ["middays"], "2.0 12.5 7.0": ["sexualize"], "19.0 19.8 9.1": ["luddite"], "-5.6 0.8 -2.9": ["transcribers"], "2.0 -0.4 10.4": ["ara"], "4.1 -7.1 11.7": ["pretaped"], "-3.8 3.8 1.3": ["deafblind"], "11.5 12.3 14.4": ["cunts"], "1.1 10.5 13.0": ["ammount"], "-7.9 1.0 4.1": ["inters"], "0.8 8.4 19.1": ["feedstuff"], "-7.4 7.6 4.9": ["miscarrying"], "16.8 5.8 8.7": ["intimidatingly"], "-0.7 3.2 32.5": ["pupping"], "8.4 11.7 8.4": ["mnemonics"], "6.0 7.2 6.0": ["lightroom"], "8.6 4.1 41.7": ["potstickers"], "13.5 6.1 6.4": ["shamefaced"], "8.3 19.0 6.3": ["goriest"], "9.4 9.2 21.1": ["sett"], "11.6 12.1 7.3": ["neologisms"], "7.4 18.3 7.7": ["longitudes"], "-3.1 1.0 1.8": ["parametres"], "5.4 18.2 4.7": ["imperviousness"], "2.4 13.4 31.3": ["veges"], "4.1 -2.1 12.0": ["propolis"], "8.0 5.5 26.0": ["cay"], "14.7 5.4 11.3": ["nanna"], "6.8 9.5 1.6": ["pitwall"], "-2.0 22.0 10.9": ["gamerscore"], "6.2 16.5 12.5": ["casbah"], "18.8 4.9 5.2": ["worlwide"], "-0.1 7.9 2.2": ["ambos"], "3.9 5.4 5.9": ["neurochemistry"], "13.0 17.5 14.2": ["senton"], "15.2 21.1 12.0": ["slimes"], "-0.6 3.4 4.7": ["discom"], "2.1 6.7 11.2": ["overlie"], "4.5 16.4 6.9": ["requited"], "5.5 8.1 27.6": ["idli"], "9.2 4.8 24.1": ["snookers"], "-0.9 6.8 12.0": ["microcirculation"], "9.6 14.0 12.2": ["efflorescence"], "11.5 4.3 7.7": ["turnoffs"], "9.5 3.1 16.7": ["snoods"], "4.2 14.3 -0.1": ["foregrounds"], "13.6 15.7 10.1": ["spinmeister"], "2.2 14.0 3.2": ["sandboxed"], "10.9 -1.7 9.2": ["hc"], "-3.2 2.1 -0.5": ["nonrecourse"], "8.7 11.4 9.7": ["stepovers"], "-8.1 3.3 1.7": ["endarterectomy"], "-2.9 2.0 2.7": ["macroeconomist"], "-6.6 0.1 3.7": ["autogas"], "-0.1 2.5 14.4": ["ranchettes"], "-4.0 1.5 3.7": ["finsihed"], "7.2 7.3 11.7": ["minstrelsy"], "11.2 5.5 10.1": ["winders"], "4.2 15.0 1.2": ["traduced"], "5.3 5.3 8.0": ["newcastle"], "14.0 -10.9 11.5": ["agrifood"], "10.2 7.7 21.2": ["sporran"], "3.7 14.3 8.5": ["arithmetically"], "21.9 14.4 23.1": ["anteaters"], "5.6 10.0 1.2": ["betted"], "2.6 9.1 1.4": ["toget"], "9.7 7.1 4.4": ["bankrupcy"], "1.2 12.5 12.8": ["offguard"], "-4.9 14.0 17.4": ["feedgrounds"], "-3.0 7.8 13.8": ["northbridge"], "-8.2 10.8 6.8": ["diversifier"], "8.7 -0.5 19.4": ["saba"], "5.3 0.7 5.1": ["foto"], "-1.6 12.0 3.5": ["didacticism"], "-5.1 13.7 6.5": ["overstress"], "11.4 4.8 7.5": ["silkscreened"], "5.7 -7.7 37.5": ["microgreens"], "-2.0 -6.0 3.1": ["implantations"], "3.8 4.6 12.9": ["outleaped"], "-3.0 15.2 12.8": ["hudud"], "0.2 4.0 17.6": ["shea"], "19.2 21.9 30.5": ["mongooses"], "0.2 10.8 11.0": ["sickener"], "9.9 9.1 7.0": ["louver"], "13.0 8.5 10.3": ["drumkit"], "-5.8 3.0 8.3": ["recalculations"], "5.8 5.9 16.3": ["rime"], "4.1 16.2 35.0": ["barberry"], "3.3 21.9 5.8": ["ennoble"], "-5.6 9.0 14.8": ["hectarage"], "0.8 -0.1 15.3": ["cachaca"], "8.3 15.7 7.0": ["transplantable"], "1.6 10.5 9.3": ["reprioritizing"], "5.9 6.5 9.6": ["postpunk"], "3.4 8.3 29.9": ["sweetish"], "8.6 12.7 15.8": ["keris"], "13.1 12.3 7.4": ["squinty"], "3.4 11.3 7.4": ["revalues"], "15.0 11.0 7.2": ["governator"], "-8.7 13.0 9.7": ["conciseness"], "12.7 21.3 14.3": ["suckering"], "7.2 -2.7 6.5": ["ati"], "5.5 4.1 6.8": ["bioeconomy"], "11.3 0.9 20.4": ["pageboy"], "13.8 6.6 11.5": ["louis"], "6.9 8.1 12.0": ["zzz"], "-1.4 6.1 5.7": ["participators"], "-0.1 6.7 10.8": ["amylase"], "8.4 13.1 9.3": ["sheepherder"], "7.1 14.8 8.6": ["vishing"], "2.5 0.5 12.9": ["vacay"], "2.5 2.3 11.5": ["tod"], "6.2 9.4 9.2": ["monumentality"], "3.6 4.4 -0.6": ["annunciation"], "-0.6 16.5 9.9": ["eulogizes"], "0.5 6.6 26.5": ["riverkeeper"], "2.0 15.4 7.5": ["bestowal"], "16.2 13.4 9.4": ["dirties"], "7.8 15.6 14.2": ["blooping"], "-4.9 14.3 4.9": ["polyamorous"], "4.6 2.8 10.2": ["sirtuin"], "-1.2 2.7 9.7": ["lookbook"], "8.0 15.7 7.1": ["tactility"], "6.2 1.2 7.0": ["stv"], "5.2 9.7 35.1": ["floury"], "-6.1 -2.5 10.7": ["birthweight"], "2.6 4.4 12.5": ["triathalon", "katulad"], "-4.2 11.9 -0.4": ["leauge"], "2.1 1.6 5.6": ["ashley"], "6.8 15.0 10.0": ["hombres"], "-1.6 0.1 5.6": ["encapsulants"], "-1.9 6.8 20.7": ["apiculture"], "7.0 12.1 0.7": ["mainspring"], "-3.0 2.8 -0.5": ["tezampanel"], "6.2 12.4 9.5": ["harrowed"], "9.6 1.6 9.3": ["reweighting"], "7.8 12.5 12.4": ["shoos"], "2.4 5.7 9.7": ["dsl"], "0.0 7.7 16.2": ["peacoat"], "11.7 1.1 8.5": ["shaw"], "-3.1 9.4 -0.8": ["disapointing"], "-7.7 7.4 9.1": ["asts"], "20.0 25.7 15.6": ["oafs"], "18.4 3.2 11.6": ["belled"], "-3.4 13.8 -3.6": ["suceed"], "18.7 22.9 13.8": ["divinities"], "4.2 11.0 9.0": ["wifely"], "-5.4 10.9 11.1": ["oth"], "5.5 1.3 19.8": ["lingam"], "3.9 17.9 8.8": ["besties"], "6.8 8.4 18.7": ["tailend"], "22.4 9.0 15.1": ["foghorns"], "7.8 8.1 9.0": ["rp"], "11.7 19.0 13.1": ["aussies"], "11.6 12.1 7.4": ["petrolheads"], "-3.0 9.4 16.0": ["letterboxed"], "21.9 16.4 40.5": ["harpooning"], "5.5 10.0 5.5": ["suffuse"], "5.1 22.4 9.0": ["multipolarity"], "-3.2 0.9 -6.3": ["assitant"], "0.2 7.1 2.6": ["niggled"], "-5.8 10.3 10.4": ["scrumhalves"], "3.5 9.6 9.4": ["tomboys"], "-3.9 7.2 12.2": ["survivin"], "3.6 4.8 9.0": ["cheol"], "-9.2 13.1 7.6": ["delineations"], "0.4 4.5 4.1": ["kgotla"], "0.5 17.3 12.3": ["nonaggression"], "-4.5 0.1 -4.9": ["neurostimulator"], "6.8 13.9 7.1": ["icers"], "-5.0 12.0 3.6": ["dedicatedly"], "-5.8 7.9 -5.4": ["eulogise"], "-1.3 18.8 7.1": ["impetuousness"], "0.2 10.3 10.4": ["minibike"], "14.2 3.2 9.9": ["chambermaids"], "14.3 -3.4 2.4": ["fitout"], "3.3 18.1 2.5": ["messianism"], "10.9 18.7 10.6": ["mundanity"], "-9.1 6.3 8.8": ["subaccounts"], "1.2 7.4 7.0": ["sating"], "-4.1 -1.9 8.6": ["preconference"], "0.0 9.6 8.5": ["nitazoxanide"], "0.9 5.0 4.0": ["economising"], "-3.5 17.5 8.7": ["disfranchised"], "0.6 14.9 12.8": ["colorations"], "10.1 11.3 7.5": ["highveld"], "-6.4 21.4 6.4": ["conflictual"], "6.4 -1.9 -2.1": ["stationers"], "3.0 8.2 9.7": ["snappish"], "2.5 9.8 13.9": ["lucha"], "5.4 7.3 17.8": ["sugarhouse"], "3.3 -5.1 3.6": ["vuh"], "-5.5 5.2 11.2": ["spodumene"], "8.5 9.6 1.8": ["overexpose"], "5.8 11.1 5.2": ["plasmons"], "-0.4 -6.6 -6.1": ["cosigned"], "4.5 6.4 11.4": ["ancestries"], "-3.5 -0.2 3.2": ["handpicks"], "-1.6 8.8 2.3": ["suppressants"], "4.3 8.2 20.4": ["chapattis"], "0.8 2.9 9.7": ["friary"], "0.7 7.4 4.6": ["saxman"], "2.0 2.6 18.2": ["colloid"], "-2.1 15.4 6.2": ["loftiness"], "-1.8 3.8 10.8": ["kahit"], "-9.2 4.4 -8.2": ["recored"], "0.2 -0.5 2.2": ["wholistic"], "-3.1 15.9 0.9": ["preventatively"], "-8.9 4.6 4.1": ["solemnize"], "8.2 2.9 7.3": ["bassoons"], "-3.4 13.1 6.0": ["lanelogic"], "8.8 5.7 18.1": ["ruffs"], "13.3 0.9 1.0": ["prang"], "-6.4 21.8 9.7": ["saheb"], "-4.7 28.0 2.2": ["delegitimized"], "2.0 1.6 2.2": ["outlots"], "1.8 13.8 12.3": ["rager"], "10.1 11.9 11.3": ["shenanigan"], "-0.9 6.9 12.0": ["ras"], "-5.8 11.5 9.4": ["racemare"], "1.8 6.4 9.4": ["liplock"], "10.7 13.9 5.1": ["hast"], "10.3 -3.6 8.2": ["cen"], "12.9 14.5 4.9": ["coverts"], "-2.4 7.3 -0.2": ["persuing"], "5.4 0.2 0.9": ["ose"], "16.0 7.3 8.0": ["soundalike"], "11.0 24.8 20.6": ["succubus"], "21.0 8.2 13.2": ["hunchbacked"], "-2.1 6.9 2.3": ["dilates"], "2.7 4.9 15.9": ["kolaches"], "-2.0 7.6 6.5": ["rsync"], "4.1 13.6 6.5": ["photosensitivity"], "11.6 19.8 5.4": ["ungentlemanly"], "11.9 8.8 19.1": ["gnu"], "5.3 23.4 15.0": ["metastasizes"], "2.3 2.7 3.6": ["nondurable"], "2.2 15.8 13.3": ["acidifying"], "7.4 -0.6 14.9": ["ier"], "3.6 21.4 11.4": ["goy"], "-1.1 5.4 0.2": ["unfiled"], "-5.2 19.6 10.4": ["tazed"], "7.6 12.1 23.7": ["tastiness"], "17.0 6.0 24.4": ["carnie"], "1.8 16.4 13.0": ["sku"], "7.8 15.2 13.1": ["hillary"], "10.6 12.4 12.0": ["dexterously"], "6.5 7.9 10.5": ["newgrass"], "5.5 5.4 14.9": ["broncs"], "2.0 10.6 12.3": ["porphyria"], "22.9 14.9 25.1": ["pinchers"], "3.6 -0.8 5.8": ["melanocortin"], "-2.4 18.0 -4.0": ["aganist"], "14.9 22.3 10.9": ["knockback"], "4.9 6.5 20.6": ["skinnies"], "12.4 1.5 15.1": ["pornstar"], "-1.8 15.7 10.6": ["reflationary"], "1.0 5.4 1.6": ["guarentee"], "1.7 9.7 6.7": ["symptons"], "-12.6 7.4 20.8": ["bermudagrass"], "-4.6 4.1 8.8": ["ameliorates"], "2.6 -4.1 4.9": ["parti"], "20.3 -7.6 17.6": ["milelong"], "-0.2 7.1 5.4": ["rhapsodizes"], "-0.7 14.0 7.6": ["hidings"], "3.6 6.7 20.2": ["wd"], "2.7 13.5 10.6": ["blusters"], "-3.9 6.0 7.6": ["anosmia"], "8.0 -1.2 2.3": ["stinting"], "4.3 7.3 7.8": ["farewelling"], "1.6 -2.6 6.7": ["nighties"], "7.2 8.6 10.1": ["unselfconsciously"], "-4.0 4.3 15.4": ["chlordane"], "0.5 1.2 2.1": ["apo"], "8.5 5.3 23.6": ["bicolor"], "-3.6 7.6 7.0": ["omalizumab"], "5.6 11.4 8.0": ["welfarism"], "20.7 2.4 3.3": ["rechristening"], "4.5 13.5 18.1": ["laird"], "-2.9 4.0 6.9": ["concerti"], "8.5 1.5 21.3": ["cockapoo"], "2.8 -1.6 9.7": ["universitywide"], "8.4 15.5 9.4": ["integrase"], "8.4 20.2 2.9": ["thunderclaps"], "5.0 17.4 18.5": ["sambo"], "15.5 13.3 -0.9": ["farmboy"], "8.9 -1.5 1.2": ["dea"], "24.4 6.3 10.0": ["gambol"], "9.7 3.8 6.6": ["soaped"], "9.9 8.0 40.2": ["gammon"], "6.5 -10.0 1.8": ["afterthe"], "2.0 -0.8 18.8": ["pancreases"], "-4.1 4.6 9.5": ["noncommital", "fraccing"], "4.4 6.5 17.1": ["orang"], "-4.0 7.8 13.5": ["biodynamics"], "1.7 12.3 12.3": ["solatium"], "22.4 19.0 15.5": ["periscopes"], "11.4 -7.7 -1.0": ["tex"], "7.0 14.6 23.9": ["oleanders"], "-0.2 11.9 10.5": ["vega"], "-0.6 2.8 6.7": ["arboriculture"], "32.5 6.8 20.7": ["gherkin"], "2.4 -5.4 14.2": ["pari"], "-1.1 -0.3 18.4": ["monotype"], "2.7 20.1 1.6": ["outmost"], "12.5 0.8 1.1": ["paybox"], "0.7 0.8 11.8": ["ketoprofen"], "-1.9 9.8 4.1": ["influent"], "1.3 -2.6 3.1": ["consulation"], "-1.5 5.4 8.9": ["excerpting"], "1.8 9.5 14.2": ["bomoh"], "-1.8 6.0 6.4": ["bugfixes"], "-1.2 9.0 6.0": ["definitley"], "5.3 22.6 5.9": ["onballers"], "3.2 6.2 3.3": ["patrimonial"], "0.0 7.6 4.7": ["tesmilifene"], "-12.9 0.9 4.4": ["colectomy"], "1.2 13.5 21.0": ["rhodopsin"], "-2.9 12.2 7.4": ["tallit"], "3.3 1.3 11.2": ["lavas"], "17.3 4.5 9.0": ["intothe"], "11.0 3.2 22.1": ["tortes"], "6.6 -6.4 5.7": ["mgr"], "-9.4 6.7 2.0": ["nitpicks"], "8.0 12.1 32.2": ["chillis"], "2.1 9.1 2.0": ["intraocular"], "-0.8 0.1 2.9": ["codices"], "34.6 12.8 6.9": ["megamerger"], "5.2 5.1 4.5": ["prefs"], "12.9 18.1 13.4": ["druglords"], "-3.0 7.9 1.6": ["interupted"], "3.1 14.9 1.6": ["illegaly"], "-4.6 4.1 6.9": ["teleserye"], "0.1 -1.2 9.2": ["rebiana"], "-9.5 6.5 8.0": ["medalling"], "8.0 6.6 23.2": ["alyssum"], "2.0 2.5 9.4": ["prepublication"], "14.2 5.9 5.4": ["tidiest"], "8.5 21.2 1.7": ["highjacked"], "4.6 1.8 20.2": ["hao"], "4.7 10.3 12.0": ["bayan"], "20.8 18.3 8.6": ["splaying"], "13.7 8.9 9.2": ["bringin"], "6.5 10.1 27.6": ["lupines"], "7.0 6.3 -3.9": ["officialy"], "6.6 9.3 10.4": ["kissable"], "-4.7 3.6 -3.2": ["treament"], "8.3 -3.9 2.5": ["nl"], "-0.1 3.2 16.9": ["hemangiomas"], "4.8 15.5 38.3": ["bucktail"], "6.7 16.1 27.7": ["brushpiles"], "14.8 4.7 7.1": ["zo"], "9.8 12.8 2.1": ["atomised"], "8.1 14.5 13.4": ["scrims"], "17.7 -5.0 19.2": ["enrobed"], "3.8 30.2 -1.5": ["genocidaires"], "3.7 10.1 32.7": ["agaves"], "8.8 -4.8 9.5": ["trona"], "7.5 9.1 15.7": ["butoh"], "-3.0 30.2 15.1": ["bollworm"], "9.6 6.9 6.5": ["turmoils"], "1.5 2.7 -6.0": ["initialing"], "5.2 13.8 8.3": ["photodetector"], "19.7 6.1 22.7": ["sawtooth"], "17.2 10.6 12.1": ["ballon"], "-2.8 6.7 6.8": ["thermistor"], "15.1 14.3 15.6": ["eyeholes"], "7.1 15.7 11.4": ["chickening"], "15.1 8.6 13.7": ["poobahs"], "4.3 8.9 -4.0": ["unpatentable"], "2.1 9.0 11.7": ["nai"], "-1.2 -1.2 11.7": ["screwcap"], "6.7 6.1 14.1": ["shortie"], "-0.8 3.4 3.9": ["haziness"], "-0.1 -5.8 20.5": ["rainier"], "-2.2 20.6 11.0": ["caddish"], "4.3 6.0 25.3": ["moreish"], "-6.2 12.3 7.7": ["neoplasm"], "2.8 14.6 4.4": ["diagnosticians"], "13.7 11.4 2.9": ["izing"], "-0.8 0.7 4.6": ["unadopted"], "10.6 12.1 12.7": ["mario"], "-2.2 3.8 8.1": ["jour"], "5.8 8.3 15.7": ["eventers"], "5.6 12.5 13.0": ["brayed"], "1.0 2.3 9.7": ["screenprint"], "2.8 28.0 7.5": ["narcotrafficking"], "3.2 11.3 17.3": ["gabacho"], "7.7 -1.8 15.7": ["orthodontia"], "6.9 13.9 20.2": ["baijiu"], "4.2 -0.3 -0.3": ["monetizable"], "6.5 1.6 9.1": ["rehabber"], "12.9 9.3 7.3": ["ingloriously"], "5.9 14.6 8.7": ["unlatch"], "-5.1 3.6 8.7": ["expressivity"], "11.0 3.3 -0.9": ["skydived"], "-4.1 19.7 -3.6": ["perserverance"], "2.6 10.1 8.5": ["hijras"], "9.9 2.6 35.8": ["stroganoff"], "10.6 10.7 21.3": ["rosebuds"], "-0.2 -2.1 17.2": ["zarzuela"], "-7.7 8.3 10.1": ["melasma"], "2.9 12.5 9.5": ["countertrend"], "-6.4 6.4 10.2": ["babesiosis"], "0.2 15.2 29.7": ["bowfishing"], "5.9 -0.4 16.1": ["peplum"], "8.2 8.6 9.0": ["dumbwaiter"], "-2.7 14.5 0.6": ["incumbant"], "-9.5 14.7 -8.3": ["impugns"], "-9.6 10.7 4.3": ["hermeneutics"], "-5.3 -0.7 17.3": ["cryopreserved"], "17.4 7.7 -2.7": ["etailer"], "10.0 5.2 4.3": ["bacteriologist"], "-0.6 1.4 13.0": ["waybill"], "2.6 -2.2 3.8": ["cer"], "13.8 9.5 13.8": ["penta"], "3.2 13.3 13.0": ["arrant"], "7.9 2.6 9.8": ["tl"], "12.2 9.9 11.1": ["agglomerations"], "0.4 9.6 6.5": ["overbook"], "1.7 22.9 6.1": ["avow"], "-6.7 6.6 3.4": ["caselaw"], "5.7 6.6 27.8": ["chewier"], "7.3 15.4 17.5": ["bodyslam"], "4.5 7.8 3.6": ["priapism"], "11.9 4.2 31.5": ["peelings"], "-8.3 -4.7 2.4": ["synthesizable"], "-1.0 4.7 7.7": ["superzoom"], "2.6 2.5 11.9": ["payin"], "-2.3 9.0 6.2": ["prophylactically"], "3.7 7.6 5.2": ["termini"], "-0.3 8.3 7.8": ["lipophilic"], "26.9 8.6 8.7": ["schoolkid"], "1.6 7.7 -1.7": ["assignor"], "2.1 12.5 12.5": ["headwall"], "4.7 19.5 14.1": ["disunion"], "-4.0 6.9 5.6": ["belongingness"], "-0.1 15.0 11.4": ["handpass"], "-2.8 5.4 4.4": ["caspases"], "13.8 13.7 8.5": ["unladylike"], "5.8 18.9 9.1": ["haplessness"], "4.9 22.6 9.4": ["venomously"], "14.3 4.6 15.3": ["splendours"], "-1.1 5.5 12.0": ["diazinon"], "9.5 8.2 -2.1": ["saavy"], "7.0 6.2 7.3": ["superalloys"], "18.9 3.2 -3.4": ["revolutionises"], "9.2 7.7 29.7": ["avocadoes"], "3.6 14.5 10.1": ["sleaziness"], "4.5 0.0 -2.0": ["hopsital"], "-7.6 21.9 -0.8": ["inerrant"], "13.6 5.0 7.1": ["louvered"], "-3.6 13.0 3.5": ["parasitics"], "-1.7 3.0 8.9": ["abbots"], "7.2 0.4 17.5": ["fou"], "-3.3 10.6 4.7": ["indictor"], "7.7 13.6 7.6": ["fetishize"], "4.8 19.6 6.8": ["godspeed"], "11.7 11.2 14.2": ["jonathan"], "-3.8 5.6 32.4": ["marsala"], "7.7 4.4 3.4": ["microcar"], "-8.9 3.1 5.8": ["microamps"], "10.8 10.7 0.6": ["possibilites"], "9.8 5.3 1.2": ["fye"], "-0.8 16.2 9.3": ["debauch"], "-7.4 4.0 1.2": ["referable"], "5.2 15.2 -1.6": ["executional"], "9.0 5.2 4.6": ["heartstopping"], "17.6 8.3 12.2": ["megapolis"], "9.0 3.8 3.3": ["allured"], "2.1 25.0 0.6": ["moharebeh"], "8.2 6.3 21.2": ["foreshores"], "-3.1 6.6 3.0": ["inforce"], "3.9 2.7 9.3": ["retractor"], "8.9 5.6 9.5": ["dreariest"], "4.7 12.9 11.6": ["barehand"], "3.5 13.3 11.4": ["daydreamer"], "3.5 5.5 1.1": ["themost"], "14.4 -1.7 17.2": ["pinafore"], "13.1 16.8 15.1": ["smacker"], "-7.0 1.3 -5.5": ["transcriptionist"], "11.9 6.3 6.6": ["breakroom"], "10.5 17.9 1.3": ["sieze"], "-1.1 -1.7 19.5": ["leadframe"], "15.7 9.6 12.4": ["mandap"], "15.1 13.2 3.2": ["inveigled"], "7.7 27.4 3.0": ["facist"], "1.9 5.0 7.2": ["adulterate"], "-1.0 5.5 12.7": ["seriocomic"], "-1.8 25.7 9.9": ["loyalism"], "-6.1 -0.0 1.8": ["perfomances"], "-5.2 2.9 4.8": ["multilaterals"], "3.3 31.5 5.7": ["misunderestimated"], "-6.9 20.0 12.8": ["deliberateness"], "-2.1 8.4 10.1": ["reformative"], "16.4 9.5 20.5": ["slobbery"], "-5.0 13.9 3.1": ["demotivating"], "18.1 9.3 17.8": ["milkmaid"], "2.1 8.8 2.4": ["hawalas"], "-5.7 4.1 3.8": ["tunability"], "4.5 12.6 10.3": ["microlensing"], "2.0 12.6 15.3": ["kickable"], "3.7 0.2 10.2": ["misprints"], "8.0 5.8 1.8": ["puting"], "-0.3 2.0 10.9": ["sorbents"], "4.9 16.3 9.1": ["sandbaggers"], "-6.2 9.4 23.8": ["semisweet"], "2.5 2.9 10.0": ["coachwork"], "5.4 0.6 10.1": ["tubercular"], "8.7 3.8 23.9": ["coneflower"], "16.6 4.4 4.2": ["modeller"], "2.7 -1.8 3.7": ["tubeless"], "-0.1 5.5 10.9": ["parasitology"], "0.9 17.9 -1.6": ["upbraid"], "7.0 9.2 12.0": ["backstrokes"], "1.3 1.3 4.5": ["backto"], "17.5 9.3 19.7": ["parkgoers"], "13.9 8.2 8.4": ["unpicking"], "-4.9 12.2 2.3": ["telecommunicator"], "4.7 7.8 -1.3": ["fwd"], "10.1 11.8 26.6": ["bola"], "12.4 5.2 29.0": ["bibimbap"], "-0.1 -5.6 3.5": ["quali"], "14.6 4.3 10.7": ["sugarless"], "-7.9 14.9 4.3": ["disconnectedness"], "9.0 5.6 16.5": ["carabiners"], "3.4 3.2 9.1": ["ered"], "-6.3 -0.0 27.6": ["hoggets"], "2.7 2.3 3.7": ["mailouts"], "13.8 16.5 11.6": ["horning"], "8.7 7.4 -2.0": ["ised"], "3.5 8.7 6.1": ["kerosine"], "15.0 4.2 14.2": ["petchem"], "-1.1 9.8 5.7": ["absorbance"], "10.1 -1.5 7.6": ["confectionaries"], "4.0 26.2 8.5": ["vengence"], "5.1 12.8 2.9": ["wanded"], "13.1 10.6 27.9": ["wattles"], "7.5 0.7 10.3": ["tablas", "earlymorning"], "3.6 -1.2 0.4": ["nitrile"], "6.3 20.2 9.4": ["flagsticks"], "0.8 6.0 -0.0": ["leukotrienes"], "-5.6 12.6 6.4": ["macrolides"], "-1.2 4.3 8.0": ["productize"], "2.3 4.5 11.6": ["superfruits"], "2.9 1.5 29.2": ["ancho"], "0.4 3.5 -3.9": ["reformats"], "3.1 16.1 16.2": ["entomological"], "6.1 7.1 4.6": ["sidepod"], "6.7 -0.1 14.4": ["dray"], "-6.2 11.8 -2.0": ["neurotrauma"], "3.1 4.0 17.2": ["laura"], "5.0 32.1 14.3": ["enchantments"], "2.7 14.6 14.3": ["gunmakers"], "7.6 4.7 4.6": ["thinners"], "13.3 0.5 34.4": ["sealskin"], "10.4 5.1 35.7": ["deboning"], "5.7 19.8 7.5": ["allright"], "11.0 -1.3 12.7": ["tock"], "11.2 3.9 3.7": ["huzzahs"], "-7.2 -2.5 6.1": ["cholecystectomy"], "5.1 8.8 14.2": ["baraat"], "19.7 4.0 6.6": ["moulder"], "5.5 -7.8 5.7": ["restitutions"], "-8.6 9.7 0.5": ["noninferiority"], "-4.2 25.5 6.4": ["intrepidity"], "6.2 4.9 16.0": ["crinolines"], "2.9 -2.2 4.9": ["ays"], "17.1 19.5 9.4": ["noiselessly"], "8.4 15.1 4.7": ["everone"], "5.1 6.3 9.9": ["slathers"], "-2.7 4.0 -0.1": ["maintenence"], "10.6 14.5 14.1": ["pleasurably"], "12.6 5.5 16.3": ["equestrianism"], "-3.5 7.5 6.8": ["vasoconstriction"], "0.2 3.8 8.8": ["fpm"], "2.7 -2.5 10.4": ["interschool"], "-2.5 -1.5 5.7": ["compering"], "15.8 4.1 8.3": ["ananova"], "5.3 4.6 10.9": ["growin"], "5.0 10.3 6.4": ["rucked"], "15.1 6.7 5.2": ["reinflate"], "8.2 7.5 21.4": ["joeys"], "7.3 3.8 9.0": ["swoony"], "10.2 9.1 22.5": ["limey"], "9.9 5.4 -1.8": ["paralympics"], "17.2 11.8 4.3": ["bossman"], "2.8 9.8 9.1": ["atmospherically"], "-1.5 -0.6 6.2": ["teduglutide"], "3.9 4.2 11.2": ["inimitably"], "-0.2 7.4 11.4": ["presidentiables"], "3.9 5.4 11.4": ["doxepin"], "8.2 4.6 16.5": ["brasseries"], "-4.0 13.7 15.0": ["permittee"], "13.5 13.5 20.6": ["rockery"], "-1.2 9.4 17.8": ["bahut"], "-6.3 -5.0 6.0": ["premedical"], "15.1 8.2 18.0": ["stirrers"], "6.1 10.3 4.5": ["spelunkers"], "5.0 13.6 9.5": ["euroland"], "1.9 7.3 17.7": ["karats"], "-6.0 13.4 5.1": ["nonfeasance"], "10.5 17.0 9.6": ["guesser"], "2.8 6.3 1.9": ["flagbearers"], "1.4 8.2 9.4": ["sidearmer"], "0.9 29.7 4.0": ["tyrannized"], "0.0 6.9 8.0": ["secretory"], "8.9 2.7 19.7": ["lou"], "2.1 11.1 13.7": ["chastely"], "18.7 -1.9 -5.3": ["codeveloped"], "2.1 -2.0 9.2": ["unch"], "5.3 1.0 14.4": ["dae"], "2.4 4.5 11.6": ["psyllium"], "-2.7 8.2 12.3": ["cocaptain"], "5.9 10.0 1.7": ["mormon"], "3.9 1.4 9.6": ["bracero"], "15.9 15.9 13.1": ["monocultural"], "3.1 16.5 1.3": ["aganst"], "10.3 7.2 12.5": ["mishandles"], "5.8 6.8 -0.5": ["anf"], "3.1 15.8 4.7": ["destabilises"], "2.8 3.3 5.3": ["biofilter"], "-2.1 0.4 7.0": ["indomethacin"], "1.5 3.8 -0.1": ["relase"], "9.4 11.6 15.9": ["supercity"], "-3.7 4.9 -2.0": ["superintendence"], "6.8 11.7 33.8": ["carps"], "-4.9 15.2 4.1": ["carefulness"], "8.0 21.5 8.4": ["reconquista"], "-4.7 8.6 8.4": ["wordsmithing"], "6.5 7.2 12.9": ["troy"], "11.2 15.5 14.2": ["airstream"], "6.6 0.9 14.9": ["slingbacks"], "3.7 13.4 11.9": ["bipedalism"], "9.3 4.8 3.5": ["occasioning"], "-1.8 12.4 12.3": ["disputants"], "7.1 26.2 10.7": ["superheroic"], "9.5 17.3 3.9": ["offsider"], "-1.1 -0.3 8.5": ["sociodemographic"], "-3.5 10.3 4.3": ["chowki"], "10.9 1.0 12.2": ["dahlings"], "11.3 4.8 0.2": ["acces"], "9.1 8.6 8.2": ["panaromas"], "4.6 -2.9 13.6": ["kwan"], "3.8 -1.2 18.4": ["citric"], "-6.0 6.5 7.0": ["cami"], "-4.3 -2.2 4.4": ["showhomes"], "10.0 3.8 5.3": ["ahalf"], "-0.5 4.8 7.5": ["rodeoing"], "13.7 9.5 23.3": ["theropod"], "1.0 7.4 13.8": ["myoblasts"], "-2.2 4.8 -1.5": ["cpm"], "10.9 3.4 5.4": ["freesheets"], "4.0 15.8 3.0": ["metaphysically"], "-5.3 3.3 5.7": ["phenobarbital"], "-8.4 25.6 -2.7": ["exactions"], "-6.1 29.4 3.4": ["overmatch"], "8.3 11.2 6.4": ["unsocial"], "1.8 3.2 15.7": ["croaky"], "-8.1 -1.4 5.7": ["amenorrhea"], "-2.9 8.2 11.7": ["timothy"], "3.7 4.4 16.8": ["microfossils"], "13.1 10.2 6.8": ["discombobulating"], "-4.5 -1.1 10.6": ["dekatherms"], "7.0 8.1 26.8": ["sauerbraten"], "-0.0 23.8 -1.2": ["legitimating"], "23.4 24.1 14.5": ["samurais"], "-0.0 5.2 18.2": ["shirttail"], "2.4 8.8 2.7": ["roadholding"], "11.9 10.6 18.0": ["banyan"], "0.8 7.8 -2.2": ["endorsee"], "2.8 17.4 20.9": ["secateurs"], "-0.9 10.2 14.3": ["geotourism"], "8.1 7.9 10.7": ["wayang"], "6.2 -1.5 5.8": ["twothirds"], "-1.3 5.0 8.6": ["xenografts"], "9.3 10.4 13.1": ["multicar"], "-7.3 15.2 0.6": ["defragmented"], "8.9 21.7 8.1": ["druglord"], "14.4 15.6 17.5": ["cawing"], "1.0 0.9 0.8": ["retransmitting"], "-1.7 14.3 2.0": ["distortionary"], "-6.6 6.1 -2.0": ["acheivement"], "5.6 5.4 11.8": ["rearend"], "-4.1 9.1 2.1": ["emoted"], "13.1 10.2 10.3": ["imperilling"], "7.0 4.7 -0.3": ["ista"], "8.5 7.0 47.0": ["wrasse"], "4.6 9.0 4.8": ["sar"], "8.3 -4.4 -3.8": ["chariman"], "5.7 6.2 13.4": ["artisanship"], "-0.4 4.0 8.6": ["karter"], "9.0 10.9 6.7": ["clumsier"], "23.4 15.9 -0.9": ["acquirement"], "3.6 21.5 10.2": ["fourthly"], "11.4 6.0 25.3": ["tankards"], "22.3 5.8 -1.2": ["standees"], "-1.4 18.5 16.3": ["ordinal"], "-4.4 6.1 -2.1": ["signalized"], "12.4 1.1 2.1": ["mgt"], "-2.3 -2.9 4.2": ["uhs"], "11.8 6.6 24.3": ["delphinium"], "4.4 12.6 21.0": ["saltiest"], "7.4 8.5 13.2": ["laban", "contumelious"], "10.9 13.7 10.0": ["thye"], "-4.0 19.7 7.3": ["compartmentalise"], "1.6 5.7 -10.0": ["controllership"], "8.0 9.2 8.4": ["jinks"], "12.1 15.1 5.2": ["fetishizing"], "-0.4 9.5 12.8": ["monsieur"], "4.7 9.7 10.9": ["redirections"], "2.3 20.2 12.8": ["phonenumbers"], "12.1 5.7 18.0": ["stuart"], "-4.4 0.4 -1.5": ["cationic"], "-4.6 17.1 25.4": ["coxswains"], "7.1 11.3 13.0": ["clouting"], "7.8 7.8 6.5": ["tangibility"], "-2.4 11.8 21.0": ["budgeters"], "8.1 0.4 0.9": ["calle"], "11.4 -3.6 9.0": ["cadillac"], "-3.5 7.9 8.2": ["postpay"], "14.4 12.4 10.1": ["odoriferous"], "25.6 9.9 9.3": ["blackhole"], "1.6 15.8 8.7": ["scrummaged"], "3.0 16.6 -5.8": ["linkman"], "-6.7 14.0 5.3": ["unpassable"], "5.0 10.6 14.8": ["eb"], "3.0 3.9 3.7": ["devestated"], "8.8 4.6 8.3": ["catenary"], "3.1 21.3 2.1": ["backstabbed"], "6.0 15.1 8.3": ["undefeateds"], "-0.8 4.9 26.7": ["marinates"], "12.0 11.3 5.9": ["copycatting"], "9.0 14.6 1.5": ["unparallelled"], "11.0 12.7 6.1": ["tricksy"], "9.8 1.7 17.7": ["browed"], "10.8 11.6 14.0": ["menubar"], "3.5 18.6 11.1": ["avidity"], "16.9 14.2 29.5": ["elks"], "3.5 9.4 19.3": ["hb"], "9.5 14.2 9.2": ["knol"], "7.3 4.8 6.1": ["squarer"], "8.0 7.1 10.2": ["voyageurs"], "6.8 0.7 16.7": ["minnesota"], "3.9 14.5 30.2": ["caladiums"], "-10.7 5.0 13.6": ["conjunctive"], "18.8 4.2 16.0": ["cancan"], "10.5 2.6 3.8": ["infastructure"], "7.2 10.6 3.8": ["easer"], "9.8 -3.5 12.9": ["rio"], "25.0 0.2 -0.2": ["entrepeneur"], "8.8 0.8 14.8": ["portland"], "2.0 9.1 5.9": ["ud"], "1.4 5.7 3.8": ["endotoxins"], "12.8 3.6 11.9": ["superclub"], "4.7 12.1 0.7": ["expatriated"], "16.4 12.6 3.8": ["showcourt"], "6.0 1.4 21.2": ["rennet"], "14.8 11.0 13.0": ["dontcha"], "1.4 -4.1 11.7": ["dor"], "2.0 8.2 6.4": ["flatteringly"], "11.8 4.4 10.0": ["busineses"], "15.4 6.6 -2.1": ["spokesmodels"], "1.9 9.9 2.3": ["copyist"], "1.1 1.1 5.6": ["kilobit"], "4.0 0.6 7.4": ["logons"], "-3.0 -6.7 11.0": ["calendared"], "0.5 3.2 1.2": ["sas"], "12.6 18.6 -5.8": ["updatable"], "-9.7 7.6 2.3": ["dysregulated"], "7.2 3.8 10.0": ["pushrod"], "15.5 12.3 34.0": ["skink"], "-2.3 8.6 9.4": ["reelectionist"], "7.8 12.2 17.6": ["luke"], "7.3 19.7 20.8": ["yachters"], "5.2 15.0 10.9": ["pussyfooting"], "6.0 5.8 18.5": ["caliche"], "1.6 8.4 3.7": ["enantiomer"], "12.3 9.7 14.1": ["rooter"], "6.9 23.0 11.2": ["hatefulness"], "3.7 21.8 6.7": ["repulses"], "7.1 13.7 26.6": ["tussock"], "5.5 5.6 6.2": ["midrace"], "17.8 19.2 11.4": ["mazelike"], "-4.2 4.7 12.3": ["disbursals"], "-4.1 -4.9 5.6": ["touchups"], "7.1 21.2 7.2": ["cowing"], "13.6 10.7 16.7": ["clickwheel"], "11.7 2.5 3.0": ["whi"], "5.2 13.0 11.5": ["raki"], "11.3 15.2 6.6": ["onlooking"], "-4.0 7.9 11.4": ["panch"], "22.3 4.0 27.2": ["knobbly"], "0.2 -4.3 5.5": ["reprocessors"], "6.4 13.4 20.0": ["snorter"], "3.1 18.3 11.7": ["warbird"], "4.2 1.8 3.9": ["distils"], "6.5 15.5 36.6": ["wader"], "3.0 7.1 7.0": ["sleazier"], "7.0 2.5 0.9": ["paralympian", "unamimously"], "-2.3 -5.5 8.0": ["plugfest"], "-0.5 8.1 10.6": ["rbs"], "1.6 13.5 1.4": ["engross"], "-6.2 9.6 8.4": ["revalidated"], "7.1 14.0 20.8": ["flatlanders"], "13.4 14.0 9.8": ["anesthetizing"], "4.3 6.0 0.4": ["deprecating"], "1.7 9.6 10.9": ["tetraplegic", "diffferent"], "15.0 7.3 11.8": ["nutted"], "3.8 1.7 13.1": ["sprayground"], "10.6 3.3 6.8": ["yoof"], "0.9 1.3 14.3": ["hamilton"], "15.7 4.7 9.7": ["monoblock"], "16.0 10.3 0.1": ["unionise"], "7.1 4.3 8.6": ["fieldworkers"], "-4.7 3.1 4.3": ["sammelan"], "-2.8 3.8 13.7": ["bassy"], "4.5 13.6 3.5": ["instantiate"], "4.5 9.7 4.2": ["tollgates"], "1.8 1.9 1.9": ["breathalysers"], "14.5 10.8 28.4": ["lotuses"], "-3.0 7.5 3.0": ["exciter"], "16.3 6.2 15.6": ["hibernates"], "1.9 6.5 5.6": ["mazar"], "7.8 17.4 8.2": ["mutilates"], "4.9 12.7 14.0": ["feeblest"], "-2.0 10.3 11.5": ["vignetting"], "2.2 -0.1 6.8": ["fortnights"], "10.4 6.1 13.4": ["catsuits"], "2.8 22.1 9.3": ["occidental"], "-2.8 23.2 19.2": ["archipelagic"], "-3.9 6.8 13.0": ["meninges"], "-3.2 -0.0 14.2": ["acetabular"], "-8.2 -4.2 6.3": ["cmt"], "13.3 8.5 35.9": ["sampan"], "12.0 9.9 8.7": ["floorings"], "12.7 3.9 7.8": ["multipacks"], "-0.2 1.4 7.0": ["agriculturalist"], "-4.1 13.7 1.7": ["responsbility"], "1.4 -2.6 2.6": ["septembre"], "4.4 11.1 10.7": ["grammarians"], "16.7 -3.7 14.1": ["lazed"], "4.4 13.3 6.4": ["interdivisional"], "6.5 7.6 3.6": ["amateurishly"], "2.5 8.6 12.1": ["combiners"], "10.9 -2.4 11.5": ["spittoons"], "5.6 -0.3 4.1": ["saddlery"], "3.8 6.5 6.0": ["outqualified"], "11.8 7.1 6.7": ["bussines"], "2.0 7.2 2.0": ["fungibility"], "4.6 2.4 11.1": ["microchannels"], "6.9 1.1 8.5": ["flophouses"], "3.6 10.4 8.3": ["highside"], "-0.6 3.7 3.9": ["salability"], "15.7 13.1 35.3": ["gaffed"], "17.8 14.6 3.4": ["whisperers"], "6.4 6.8 11.0": ["fac"], "10.3 1.8 5.7": ["sn"], "2.0 4.1 -2.8": ["einem"], "5.8 27.7 5.9": ["coreligionists"], "10.4 8.9 6.5": ["inexpert"], "7.6 20.1 10.5": ["scientism"], "-11.3 2.7 17.1": ["vomitoxin"], "14.3 7.9 10.9": ["disassembles"], "-5.8 5.0 -4.1": ["anaesthesiologist"], "14.0 20.1 14.5": ["hindmost"], "8.1 17.5 6.7": ["crepuscular"], "12.2 4.4 19.6": ["cgi"], "16.3 14.1 4.8": ["incinerates"], "0.7 4.3 12.7": ["startin"], "1.2 10.7 2.7": ["microgrids"], "7.9 6.8 12.3": ["pinon"], "7.3 1.3 9.8": ["dyer"], "-2.4 17.9 4.9": ["unclouded"], "-7.6 18.4 4.6": ["carbapenems"], "4.2 14.0 17.2": ["lovey"], "-6.1 8.9 -2.4": ["quantifiably"], "7.4 14.3 5.9": ["totaly"], "9.0 16.3 8.0": ["jugglery"], "1.4 1.8 34.2": ["braises"], "11.7 15.8 13.3": ["crim"], "3.3 16.0 22.0": ["roadbeds"], "12.2 17.0 20.0": ["cankerworm"], "3.7 2.2 10.1": ["const"], "3.2 10.4 2.5": ["jumbling"], "11.7 10.7 15.3": ["paraders"], "8.5 5.2 2.6": ["securitising"], "1.5 6.0 10.2": ["serine"], "14.2 5.6 15.4": ["puce"], "-1.5 0.0 29.6": ["cheddars"], "0.2 4.1 11.1": ["subfields"], "11.3 18.9 10.7": ["doubtfully"], "11.0 24.3 0.8": ["securocrats"], "-4.3 -8.6 1.2": ["empanelment"], "9.0 10.7 12.2": ["aborigine"], "1.3 11.7 6.9": ["politest"], "16.7 10.2 30.1": ["trailside"], "-4.5 4.7 5.5": ["tobramycin"], "7.1 6.2 32.8": ["hashbrowns"], "6.1 6.8 31.8": ["threshers"], "-5.7 0.6 6.9": ["bedrest"], "-1.6 20.5 2.7": ["mostest"], "8.8 8.1 29.1": ["betta"], "14.3 13.3 13.0": ["rapscallion"], "9.7 12.1 37.1": ["curlew"], "10.8 12.1 15.8": ["bootlaces"], "10.8 7.2 7.7": ["frontrow"], "6.2 14.0 11.0": ["sleepwalkers"], "8.4 8.9 4.7": ["chiptune"], "3.5 7.5 7.3": ["pyong"], "9.6 9.3 3.6": ["rhe"], "1.9 7.8 2.6": ["demographical"], "-0.8 23.0 9.9": ["polemicists"], "3.0 -8.2 -1.3": ["acccording"], "8.5 7.2 3.0": ["unreviewed"], "8.8 6.1 11.8": ["filmstrip"], "9.1 5.4 -9.7": ["acess"], "2.0 23.6 11.7": ["sexists"], "10.3 10.8 19.4": ["whiteface"], "8.7 14.8 8.2": ["quanta"], "-4.0 14.4 7.1": ["noirs"], "5.3 0.2 23.9": ["majolica"], "5.0 23.0 3.0": ["debunkers"], "4.8 15.1 7.6": ["interstices"], "6.1 33.0 1.8": ["weaponised"], "1.5 8.1 18.8": ["farang"], "7.9 16.3 9.4": ["declaw"], "5.2 3.5 2.0": ["nanosystems"], "5.9 13.9 21.1": ["moochers"], "3.1 -7.8 6.3": ["espanol"], "16.7 2.5 9.0": ["hobs"], "-1.4 6.8 3.0": ["pratice"], "9.8 2.6 21.3": ["vermiculture"], "4.2 19.2 6.4": ["inconstant"], "-1.8 1.6 3.5": ["reteamed"], "3.7 7.3 6.4": ["buiding"], "18.2 30.2 7.2": ["malevolently"], "6.8 13.7 38.3": ["sticklebacks"], "8.2 8.3 7.7": ["excretory"], "7.8 10.8 4.5": ["theo", "identitiy"], "14.2 3.3 2.0": ["untangles"], "12.9 8.5 -6.1": ["blipped"], "9.0 18.1 10.8": ["droppin"], "-1.2 5.1 0.8": ["differmaterially"], "14.2 6.0 8.5": ["rustbelt"], "15.9 13.8 19.6": ["horsehide"], "-18.4 6.8 5.5": ["preceptors"], "4.4 7.4 10.8": ["ino"], "14.5 7.9 17.7": ["baa"], "4.0 15.1 10.9": ["goonda"], "-4.8 3.9 8.7": ["deinstitutionalization"], "2.3 14.8 10.3": ["purgative"], "-2.2 8.2 12.9": ["buyrate"], "-8.0 13.0 5.9": ["quorums"], "-0.8 -0.3 9.9": ["saleyard"], "12.3 15.2 12.0": ["cakewalks"], "5.6 17.0 8.2": ["scrappiest"], "-1.5 9.7 15.5": ["supergene"], "20.1 17.1 4.4": ["nightmarishly"], "10.3 13.8 21.8": ["foxhounds"], "9.3 11.7 19.8": ["papi"], "6.6 8.6 18.5": ["biogeography"], "3.1 11.4 -1.3": ["problematically"], "-0.0 -1.7 5.3": ["kinesiologist"], "15.9 0.8 -4.8": ["mobil"], "-9.1 5.6 14.9": ["noninstructional"], "12.6 7.2 1.2": ["memristors"], "11.4 13.6 14.6": ["bullhook"], "-0.6 8.0 10.2": ["nailbiters"], "7.5 18.5 14.8": ["nomenklatura"], "-9.0 17.3 4.9": ["surah"], "14.9 13.4 16.5": ["mendicant"], "11.8 1.1 6.2": ["gro"], "10.2 3.0 4.4": ["cfo"], "21.0 8.6 24.8": ["moai"], "8.0 7.6 12.6": ["expediter"], "6.2 7.0 8.6": ["scatted"], "-1.1 6.9 13.9": ["flavonols"], "11.3 2.0 8.9": ["kittenish"], "-1.0 4.9 -1.1": ["pergolide"], "11.1 5.4 8.7": ["nou"], "-5.1 6.9 11.3": ["incenses"], "5.2 6.0 20.0": ["tounge"], "-4.3 3.4 4.8": ["cochairs"], "9.6 10.6 7.9": ["gaslight"], "3.2 17.6 5.0": ["watchfully"], "12.9 5.8 11.7": ["superconference"], "9.3 9.4 23.8": ["ironwood"], "-4.5 0.1 7.1": ["blepharoplasty"], "7.9 14.9 12.5": ["mechanize"], "2.3 6.5 14.3": ["rachel"], "21.0 2.8 10.3": ["highfliers"], "13.7 4.8 30.6": ["beignet"], "16.6 18.7 9.1": ["disembowelled"], "-3.6 6.9 13.1": ["unraceable"], "-0.3 16.2 36.3": ["waterfowling"], "14.0 8.3 13.0": ["boogies"], "13.0 7.0 10.2": ["soundsystem"], "16.9 26.7 13.3": ["archangels"], "15.1 6.3 2.9": ["cosied"], "13.4 3.2 34.1": ["kipper"], "14.4 6.3 40.2": ["oystercatchers"], "11.6 9.8 5.8": ["trackpads"], "12.0 9.3 32.5": ["ibises"], "2.9 10.1 11.5": ["intemperance"], "12.3 3.7 11.1": ["pica"], "8.3 3.9 11.8": ["offputting"], "8.3 7.2 11.1": ["pansexual"], "3.8 6.7 28.5": ["seiner"], "10.0 13.0 7.0": ["ars"], "0.5 16.4 8.7": ["utterings"], "3.2 17.0 8.3": ["unteachable"], "-1.8 8.7 17.7": ["sportbikes"], "-1.4 16.3 -4.5": ["incriminates"], "4.0 5.0 13.4": ["scrotal"], "1.1 9.6 6.5": ["tunefulness"], "4.5 10.7 5.6": ["apeshit"], "13.5 8.0 -5.6": ["linkups"], "2.4 13.0 27.1": ["jetskis"], "12.1 4.7 5.8": ["behaviorists"], "6.0 -0.8 12.6": ["mia"], "11.6 20.5 13.5": ["onomatopoeia"], "14.3 27.4 16.2": ["doughboys"], "9.4 11.1 14.3": ["granulomas"], "8.4 12.4 5.1": ["fromt"], "0.1 9.1 5.9": ["newsmaking"], "-4.5 -5.3 -1.9": ["questionaire"], "25.8 8.1 17.4": ["smooshed"], "0.2 15.9 6.1": ["deiced"], "15.9 12.8 6.9": ["fends"], "1.8 0.6 -1.1": ["medspa"], "-11.3 9.7 4.2": ["pollworkers"], "17.8 9.9 22.7": ["throwdowns"], "14.3 13.1 17.7": ["cheekiest"], "24.0 12.9 9.8": ["carbuncle"], "6.6 0.7 4.7": ["softgoods"], "4.3 7.7 13.1": ["scorchers"], "-2.0 20.8 6.4": ["pally"], "8.6 6.4 16.8": ["bakeshop"], "-3.7 2.4 0.1": ["liquidities"], "1.5 10.7 4.5": ["tantra"], "9.1 15.1 11.6": ["homogenisation"], "6.5 12.2 7.9": ["gettting"], "9.6 7.1 6.6": ["brushoff"], "3.6 13.6 4.1": ["placidity"], "1.1 8.1 9.0": ["underweighted"], "17.7 1.3 8.0": ["pharm"], "2.3 -3.5 6.9": ["platemaking"], "-2.6 0.4 2.7": ["milligrammes"], "-2.3 9.6 3.5": ["immunomodulator"], "7.1 7.5 20.6": ["mithai"], "3.6 8.2 11.8": ["whens"], "4.3 -1.1 25.5": ["farmstand"], "-4.3 6.3 4.9": ["groundbreakers"], "4.8 11.1 0.5": ["immunotherapeutics"], "7.5 6.3 10.6": ["slashings"], "12.1 5.2 20.7": ["sui"], "1.7 8.6 5.7": ["acrolein"], "-6.9 -3.6 12.9": ["waitlists"], "-1.3 14.4 1.6": ["proselytized"], "1.0 1.1 30.6": ["quinces"], "7.7 9.6 36.8": ["salsify"], "6.9 24.6 7.3": ["crueller"], "-2.0 1.1 -3.3": ["trainsets"], "6.9 -1.3 -1.8": ["fradulent"], "7.8 8.9 3.1": ["dap"], "5.1 1.2 23.7": ["pai"], "3.3 12.2 1.5": ["construes"], "2.9 7.9 -1.2": ["confabulations"], "1.4 4.1 4.3": ["outdrawing"], "-3.1 -2.0 13.6": ["oligo"], "-6.2 4.5 5.0": ["candidiasis"], "-3.8 6.7 1.2": ["interpolations"], "16.5 12.3 12.0": ["waggled"], "0.1 17.0 10.8": ["gradualist"], "8.7 8.9 3.9": ["ecstasies"], "-7.0 6.9 6.5": ["maribavir"], "11.7 18.9 11.8": ["terraforming"], "7.5 15.0 2.3": ["forebearance"], "16.7 10.9 9.2": ["autocomplete"], "-9.4 8.4 10.9": ["radioiodine"], "13.1 14.1 14.6": ["fisheye"], "1.5 10.6 5.0": ["mylo"], "4.4 6.5 3.0": ["theatric"], "3.3 11.6 12.9": ["unessential"], "3.8 8.1 11.7": ["corticosterone"], "0.7 5.8 8.4": ["mahurat"], "5.8 6.3 3.0": ["procurator"], "0.7 4.0 8.9": ["zircons"], "11.6 9.7 8.6": ["lousiest"], "5.6 3.7 26.1": ["chimichangas"], "5.1 8.8 3.4": ["memorability"], "4.7 19.0 21.6": ["larvacide"], "2.2 15.2 3.2": ["fogginess"], "1.2 12.8 8.0": ["interrogative"], "9.7 4.3 20.4": ["warner"], "-2.5 12.3 7.3": ["mythologizing"], "3.3 8.4 7.0": ["deleveraged"], "7.4 8.6 10.4": ["alabama"], "5.1 14.5 10.0": ["tamped"], "3.6 8.0 19.7": ["feeing"], "0.5 6.9 6.4": ["teetotallers"], "-1.8 7.5 7.2": ["athelete"], "1.1 2.0 7.0": ["lso"], "3.4 5.8 16.1": ["teletimer"], "0.8 -2.8 25.4": ["sweetgrass"], "-2.7 9.4 13.0": ["nearfalls"], "7.3 8.1 18.0": ["spasmodically"], "1.2 8.2 15.2": ["adulterants"], "2.7 -5.2 -1.8": ["octobre"], "10.4 15.2 19.5": ["flints"], "7.3 14.6 12.1": ["tooltips"], "2.1 7.5 4.4": ["decsion"], "-0.0 20.2 9.0": ["firelines"], "3.7 3.7 3.0": ["lusher"], "16.8 17.0 10.2": ["oxymorons"], "5.9 -10.5 10.0": ["clude"], "4.4 20.7 14.5": ["fumbler"], "6.1 12.8 7.8": ["transposon"], "7.0 10.6 0.6": ["sleepwalks"], "10.4 8.3 6.0": ["chanters"], "7.4 21.2 -0.3": ["unpresidential"], "15.9 0.2 7.4": ["supergraphics"], "10.2 0.7 -3.3": ["extoll"], "-2.1 3.5 0.2": ["interventionalists"], "6.3 11.4 9.7": ["flashcard"], "-1.5 3.1 12.1": ["rancheria"], "6.3 0.9 1.2": ["sation"], "2.8 26.5 7.8": ["chivalric"], "7.8 16.1 31.8": ["tenderest"], "11.7 15.7 21.5": ["barrens"], "7.4 9.4 9.8": ["dumbasses"], "-3.6 4.1 11.9": ["minoxidil"], "-1.8 11.8 16.2": ["poblacion"], "1.6 11.8 27.0": ["whoopers"], "1.0 2.0 13.7": ["lagi"], "-5.1 7.7 9.5": ["cofactor"], "0.1 3.5 8.5": ["leavens"], "14.5 21.6 0.4": ["hacktivist"], "2.3 2.1 5.8": ["lenghty"], "-14.1 1.5 6.1": ["addded"], "-3.1 16.4 13.8": ["nanoshells"], "6.2 18.7 10.5": ["demagoguing"], "-11.3 6.4 6.4": ["teleclass"], "4.1 11.5 5.6": ["tablature"], "8.7 5.4 5.6": ["agey"], "6.3 12.5 8.0": ["overmuch"], "-4.3 9.4 10.5": ["vanua"], "10.7 8.6 4.3": ["counterprotests"], "-1.6 5.4 3.2": ["adsorbent"], "8.7 5.0 4.3": ["underfire"], "-5.3 6.1 9.9": ["roadmaster"], "10.1 5.3 4.6": ["bulding"], "5.4 12.3 4.0": ["blathered"], "18.3 12.3 18.5": ["americana"], "0.3 18.2 8.0": ["lebanon"], "0.4 6.0 13.7": ["wheatbelt"], "5.8 5.2 7.1": ["kann"], "21.4 -6.4 13.0": ["beribboned"], "1.4 14.6 6.5": ["undesirability"], "9.4 -3.5 -1.9": ["vah"], "2.8 20.8 6.4": ["bosons"], "11.5 5.6 13.3": ["navratna"], "7.2 3.2 14.1": ["sambas"], "5.1 13.8 27.1": ["vetch"], "-10.1 9.2 2.2": ["docudramas"], "9.2 10.4 12.0": ["vegging"], "3.6 11.4 1.8": ["electroencephalogram"], "2.2 9.4 5.5": ["crorepatis"], "-3.1 22.2 3.7": ["determiner"], "-10.1 15.1 4.3": ["perceptiveness"], "0.4 18.1 1.3": ["unreviewable"], "4.6 7.6 8.8": ["summariser"], "-3.3 4.0 17.9": ["mangalsutra"], "-1.5 -2.2 3.9": ["acappella"], "3.0 36.6 5.5": ["dissuasion"], "13.1 5.4 18.8": ["skinner"], "7.3 10.0 2.2": ["decontrolled"], "7.8 4.7 33.1": ["macadamias"], "4.6 4.1 45.7": ["milkfish"], "-3.9 10.7 9.2": ["chacha"], "2.2 11.5 4.4": ["unexpectedness"], "0.2 7.2 10.2": ["neil"], "11.7 27.3 14.7": ["anothers"], "7.8 2.2 22.9": ["shuttlecocks"], "11.9 10.6 13.1": ["gesticulate"], "10.2 18.7 34.2": ["stoat"], "-6.0 8.8 -12.0": ["cardiological"], "12.3 13.6 25.8": ["pretties"], "6.4 20.2 7.6": ["rinderpest"], "20.4 9.8 -4.8": ["launced"], "3.4 6.4 34.4": ["guac"], "3.8 6.0 14.1": ["distaffers"], "-5.6 1.4 8.2": ["downsizers"], "1.0 8.4 4.3": ["retyping"], "3.0 -3.8 10.2": ["trunkline"], "-0.1 9.0 6.8": ["picaridin"], "-8.1 14.8 3.2": ["khalwat"], "7.9 22.8 9.7": ["malingerers"], "-4.5 14.2 5.4": ["osteopontin"], "5.7 8.7 -4.8": ["reconversion"], "15.9 13.5 30.6": ["breadcrumb"], "10.6 12.4 13.7": ["trollop"], "-5.0 2.8 1.7": ["pgs"], "8.7 7.2 7.9": ["appartment"], "5.9 3.9 7.4": ["lincoln"], "16.3 2.8 7.1": ["ensnarled"], "-3.1 18.3 -0.8": ["psychical"], "15.4 -10.1 -6.8": ["announed"], "12.9 14.1 9.0": ["noisome"], "1.2 13.2 16.5": ["chloroplast"], "-10.3 4.7 -4.0": ["clamed"], "14.4 11.1 12.0": ["infantilism"], "-11.7 9.4 11.6": ["unschooling"], "7.2 0.1 17.5": ["batiks"], "-5.7 6.6 6.4": ["darbepoetin"], "4.9 1.7 4.9": ["mmcmd"], "-13.7 4.1 5.4": ["myomectomy"], "-0.0 -0.8 11.4": ["phenylketonuria"], "1.2 13.5 9.2": ["monasticism"], "8.7 16.8 11.7": ["windmilling"], "11.2 16.4 9.8": ["denude"], "4.1 0.5 15.1": ["mucin"], "-5.5 5.0 0.0": ["practioner"], "-7.5 9.2 8.4": ["polyandry"], "-4.8 7.4 9.6": ["bumiputras"], "1.4 2.4 5.7": ["wiith"], "6.2 0.0 4.7": ["roadhouses"], "-3.6 16.1 4.4": ["factionalised"], "7.5 0.0 17.7": ["murray"], "-3.0 -3.0 5.6": ["flexitime"], "15.6 1.4 10.2": ["bunfight"], "7.7 20.1 6.2": ["nuthouse"], "-4.5 8.8 -1.7": ["mobiliser"], "13.3 14.3 1.3": ["claque"], "18.8 4.8 4.2": ["tata"], "-0.9 -2.4 16.9": ["singlespeed"], "-4.4 8.7 15.3": ["winegrowing"], "11.4 -1.9 6.8": ["metalized"], "-5.0 8.8 4.6": ["relaxant"], "27.1 4.2 11.0": ["overhung"], "26.6 10.6 14.4": ["thwacking"], "7.1 12.1 8.0": ["demises"], "9.2 3.4 35.1": ["fatback"], "-0.9 1.5 9.7": ["emarketing"], "1.5 -1.3 9.2": ["dancewear"], "-14.2 8.5 1.3": ["beleives"], "12.7 5.5 27.5": ["dormice"], "22.7 2.1 9.8": ["yonks"], "2.0 8.7 3.2": ["empathises"], "-2.4 31.5 -3.8": ["strongpoint"], "-0.0 0.0 1.9": ["fobbed"], "10.8 -0.3 9.7": ["metallurgic"], "13.5 20.4 23.7": ["horsetail"], "-8.6 17.0 -7.7": ["incontestably"], "-2.2 13.7 5.6": ["grippingly"], "7.9 -0.5 4.9": ["biorefining"], "1.0 13.8 9.8": ["fervency"], "-0.7 8.7 1.2": ["grillings"], "16.5 16.1 6.7": ["encyclopaedias"], "-9.7 10.9 10.0": ["kaupapa"], "9.1 8.7 8.5": ["intercoolers"], "7.0 6.3 -1.9": ["presure"], "0.3 3.6 5.5": ["elastography"], "4.3 3.8 -2.4": ["withold"], "3.6 4.1 10.6": ["ips"], "-4.5 -2.8 2.7": ["reissuance"], "10.8 7.4 7.5": ["touchiest"], "-4.4 10.2 19.7": ["shyer"], "11.4 17.4 14.7": ["preposterousness"], "-7.6 5.8 -2.8": ["shp"], "4.8 8.8 0.8": ["professionalised"], "4.5 11.8 -1.6": ["commandingly"], "3.0 11.9 17.6": ["freeriding"], "-1.1 22.8 -1.8": ["undergrounds"], "9.1 11.1 20.3": ["unleavened"], "0.8 10.3 21.9": ["cassia"], "5.7 1.6 34.3": ["proscuitto"], "4.2 10.6 14.2": ["mestizos"], "27.4 13.7 25.2": ["blobby"], "-10.0 13.1 2.2": ["challengeable"], "4.5 6.1 45.7": ["flatties"], "-8.3 3.9 6.2": ["nitrobenzene"], "6.8 3.4 17.6": ["cyclo"], "11.9 13.6 6.7": ["palls"], "3.5 1.2 9.2": ["flavanol"], "-8.8 -2.2 1.2": ["volved"], "10.0 8.1 17.9": ["guesstimated"], "12.5 11.1 6.9": ["codswallop"], "1.2 17.6 11.1": ["likings"], "-3.2 10.9 -8.4": ["audibility"], "-3.3 3.8 15.3": ["monkhood"], "0.5 12.7 9.3": ["depsite"], "9.9 12.9 9.3": ["crappier"], "0.8 16.3 8.9": ["indeterminable"], "-9.5 12.1 4.5": ["playes"], "-0.3 8.0 13.0": ["peds"], "13.4 15.2 12.2": ["hacksaws"], "-7.3 -0.2 0.9": ["promethazine"], "13.8 17.0 4.5": ["monstered"], "0.5 3.1 11.8": ["sib"], "8.7 11.2 39.2": ["pacu"], "10.0 18.7 3.8": ["pyrrhic"], "10.8 12.7 12.4": ["apis"], "16.5 12.6 16.2": ["schnoz"], "1.9 10.1 8.4": ["carryon"], "-1.1 14.2 12.8": ["forbearing"], "-4.2 6.1 13.5": ["rong"], "3.8 20.4 4.3": ["adepts"], "2.5 32.8 15.6": ["paladins"], "8.2 11.7 7.5": ["ranchlands"], "1.0 9.9 44.8": ["brant"], "-7.4 -0.8 16.6": ["reweigh"], "5.6 1.7 11.9": ["tole"], "11.9 5.8 4.8": ["talkathon"], "16.4 13.9 10.9": ["cannister", "roamin"], "-1.7 2.2 4.3": ["emiratisation"], "3.7 6.2 12.6": ["flim"], "-1.6 13.2 15.0": ["seedbeds"], "-2.6 1.8 16.4": ["clearways"], "2.9 3.5 5.1": ["hydride"], "12.9 9.6 11.0": ["yaps"], "2.7 6.7 -2.4": ["prevaricated"], "13.4 9.0 17.5": ["uvula"], "1.5 8.6 14.0": ["grouted"], "21.1 18.7 -0.6": ["antigravity"], "-6.8 13.9 9.0": ["telangana"], "10.1 6.9 10.0": ["tingled"], "1.3 13.4 8.7": ["bifocal"], "-0.7 2.9 -1.0": ["sensitizes"], "19.2 -0.3 7.5": ["baulks"], "6.0 16.9 12.9": ["locution"], "5.4 16.1 49.7": ["sportfish"], "15.5 10.4 5.8": ["ascendent"], "2.4 3.7 14.2": ["sutra"], "18.3 8.7 7.9": ["palmtop"], "5.1 16.9 -0.4": ["personell"], "4.4 7.2 7.6": ["underinflated"], "2.4 20.3 25.3": ["rodenticide"], "5.4 19.1 18.1": ["disfigures"], "20.7 6.8 4.6": ["vidgame"], "1.6 5.3 6.8": ["biogeochemistry"], "6.1 17.6 14.6": ["disembowelment"], "-5.1 1.7 4.9": ["adjudging"], "-2.2 -7.7 5.2": ["carnitine"], "-5.5 9.0 11.8": ["autonomies"], "2.2 31.2 1.4": ["bombmakers"], "6.1 10.3 9.7": ["polynomial"], "13.5 -0.2 1.4": ["commericals"], "18.6 8.1 22.8": ["pulchritude"], "34.5 21.0 41.2": ["mantis"], "6.8 21.4 -1.6": ["conspiracists"], "-0.0 4.0 14.8": ["woolgrowers"], "-8.1 4.7 7.1": ["summitted"], "4.5 6.2 20.2": ["argillite"], "-1.4 11.6 -3.8": ["restituted"], "7.5 2.2 8.1": ["gine"], "-3.4 13.3 -5.0": ["diferent"], "-3.8 7.8 5.3": ["decrement"], "9.4 -4.7 14.5": ["sheepskins"], "-1.8 9.8 13.9": ["complementation"], "6.3 21.5 1.5": ["susceptibilities"], "5.4 7.1 -0.8": ["porfolio"], "8.3 12.2 16.8": ["sambuca"], "16.5 15.4 5.1": ["worrywarts"], "12.5 3.6 5.5": ["riffling"], "10.6 14.6 8.3": ["combiner"], "13.1 10.6 9.5": ["trailor"], "11.7 7.7 14.7": ["kerogen"], "6.4 10.4 5.0": ["harmfulness"], "9.0 -1.8 2.1": ["zation"], "-3.5 12.9 6.3": ["confessors"], "-5.1 12.7 7.5": ["myeloid"], "5.3 13.7 19.6": ["woodcutters"], "10.6 -1.6 22.8": ["kraft"], "-2.0 -6.1 -1.2": ["arbitrates"], "19.6 12.1 15.7": ["superhot"], "3.5 3.7 16.5": ["hepatocyte"], "-5.8 0.5 9.4": ["agistment"], "5.0 3.9 7.7": ["scoldings"], "0.1 1.8 12.6": ["antiaging"], "13.4 14.0 13.3": ["oooo"], "4.1 12.6 11.7": ["worsted"], "11.6 7.8 8.6": ["popcorns"], "7.7 7.6 -0.6": ["actualising"], "6.6 3.3 -1.7": ["surpised"], "18.6 2.8 12.9": ["badboy"], "-4.3 8.6 2.1": ["immunologically"], "-0.8 -1.1 27.8": ["satsumas"], "5.1 3.4 11.9": ["laughers"], "-1.5 4.4 20.2": ["garri"], "3.1 3.8 12.4": ["drm"], "-1.7 3.4 5.6": ["digresses"], "5.2 -3.9 4.7": ["proces"], "23.5 11.9 21.5": ["poxy"], "2.0 26.3 9.2": ["egoist"], "14.2 7.7 13.6": ["unironic"], "7.6 0.4 16.6": ["joseph"], "-9.2 2.7 -0.0": ["outpoll"], "-4.9 -1.9 -1.0": ["electrotherapy"], "6.2 0.3 4.5": ["webspace"], "2.5 7.8 3.8": ["diffractive"], "-0.6 15.2 9.7": ["carnapping"], "9.8 9.3 13.1": ["monkeying"], "18.3 12.8 19.2": ["dalmatian"], "17.1 1.0 4.6": ["automative"], "5.6 7.7 6.4": ["possiblities"], "7.2 8.7 11.4": ["shaggles"], "1.7 15.4 7.0": ["repressor"], "4.2 2.8 14.9": ["hemangioma"], "-0.3 2.7 15.2": ["fingerstyle"], "6.4 6.6 10.2": ["swaptions"], "16.9 4.0 7.9": ["bya"], "-4.1 0.6 14.9": ["subadvised"], "10.6 14.1 18.8": ["sucka"], "3.8 10.6 -4.9": ["aggresively"], "12.0 17.2 5.4": ["superagent"], "3.4 13.6 2.6": ["inferential"], "14.1 11.1 16.9": ["blacklight"], "4.2 22.9 3.6": ["nonphysical"], "2.5 23.8 14.6": ["virtuously"], "2.7 4.6 13.2": ["sugarbeet"], "2.5 3.1 10.4": ["cheeriest"], "6.0 -0.0 7.8": ["airier"], "0.3 14.3 6.7": ["leadout"], "1.4 -1.8 5.1": ["maquila"], "7.0 -0.1 29.4": ["panamax"], "18.1 17.1 39.1": ["manta"], "6.1 8.9 13.9": ["oor"], "5.2 12.2 14.6": ["dukedom"], "-3.8 -4.2 8.2": ["crosscountry"], "12.8 4.9 23.9": ["ungreased"], "-4.3 4.9 19.6": ["flaxseeds"], "12.6 0.4 9.6": ["chapstick"], "8.2 15.5 -5.6": ["falled"], "8.5 11.6 7.7": ["segway"], "11.6 1.0 19.1": ["trivets"], "-2.1 19.4 11.7": ["moralities"], "6.2 9.3 5.1": ["nanoemulsion"], "2.4 0.6 15.2": ["macerated"], "-14.6 13.8 1.5": ["polypharmacy"], "0.9 21.7 7.4": ["deist"], "14.3 8.2 26.2": ["burl"], "5.0 8.2 -6.8": ["ratiopharm"], "7.7 9.3 17.3": ["ichi"], "9.9 23.1 10.8": ["portentously"], "-5.5 -4.9 22.0": ["wethers"], "-0.8 18.6 5.8": ["freekicks"], "7.4 4.6 -3.5": ["swopping"], "-0.3 0.5 9.3": ["scarification"], "0.8 6.9 16.6": ["traditionals"], "22.0 7.4 10.6": ["gobsmacking"], "-1.1 8.8 5.0": ["outrushing"], "4.8 5.5 8.2": ["wisconsin"], "-8.0 -4.6 1.4": ["aded"], "9.6 7.8 18.3": ["spritzer"], "-6.3 5.9 14.1": ["tuberose"], "1.3 1.9 5.9": ["youthfully"], "0.7 17.3 4.9": ["exhilaratingly"], "13.7 9.4 12.6": ["boi"], "19.3 4.5 20.1": ["trussing"], "10.7 1.7 12.7": ["hk"], "17.9 9.8 0.9": ["bigshot"], "-2.7 11.5 8.7": ["sexsomnia"], "7.0 10.3 14.3": ["synthy"], "-4.5 16.4 -0.4": ["refutations"], "1.7 -1.4 8.6": ["ibang"], "6.1 15.6 13.2": ["palpitating"], "17.1 7.9 29.9": ["molly"], "3.9 21.2 9.6": ["virality"], "1.9 9.4 39.1": ["chinooks"], "11.4 17.2 5.3": ["prostrating"], "9.3 12.0 3.0": ["hamfisted"], "3.5 2.2 -0.8": ["homeworkers"], "2.8 25.9 3.7": ["iraqi"], "-2.0 1.6 12.0": ["elution"], "12.4 5.7 8.4": ["fanfest"], "15.7 10.2 12.0": ["hoodoos"], "2.8 8.0 7.1": ["townland"], "9.4 4.4 2.6": ["pilled"], "6.9 9.3 10.5": ["binomial"], "11.2 9.4 11.3": ["cokehead"], "-2.3 1.9 3.8": ["nondiabetic"], "4.2 13.8 6.3": ["strangulate"], "6.4 10.6 19.4": ["overfeed"], "-0.0 18.6 13.5": ["lechery"], "13.8 25.8 13.4": ["corporatocracy"], "8.0 4.1 15.4": ["basaltic"], "1.2 11.3 -6.7": ["ians"], "17.4 6.7 8.4": ["douches"], "8.1 8.7 13.7": ["colleen"], "12.1 20.0 16.4": ["raiment"], "-6.3 10.7 5.4": ["prochoice"], "19.1 6.6 6.6": ["scamster"], "10.3 8.8 -2.5": ["visualises"], "8.4 14.6 3.1": ["shoddiness"], "6.3 6.1 2.8": ["divines"], "15.7 14.0 25.5": ["langur"], "-0.5 11.4 -1.8": ["sikh"], "11.9 11.9 14.4": ["twats"], "8.5 7.4 17.7": ["hatters"], "4.9 9.2 6.2": ["indecorous"], "7.4 6.2 -1.2": ["invisibles"], "7.1 3.4 18.4": ["emily"], "-0.7 15.2 7.7": ["circumspectly"], "1.1 11.9 9.1": ["palletized"], "10.5 -0.6 9.7": ["yy"], "-1.3 5.9 31.4": ["oiliness"], "2.2 1.0 4.8": ["photobooks"], "9.7 3.2 1.1": ["unfasten"], "-2.3 9.3 -10.0": ["disassociating"], "11.2 12.7 17.1": ["beeches"], "-8.0 12.9 0.6": ["dacarbazine"], "6.7 3.6 31.0": ["zabaglione"], "1.1 6.2 11.9": ["snowslide"], "1.1 0.9 34.1": ["posole"], "13.8 25.2 7.9": ["flyboy"], "6.0 14.6 11.4": ["pointillist"], "-3.4 5.4 10.0": ["vascularization"], "-2.1 9.5 16.2": ["eucharistic"], "7.1 27.4 1.7": ["miliary"], "-0.1 13.5 13.5": ["cohabitants"], "7.0 9.0 2.2": ["hundreth"], "-3.0 20.7 8.9": ["palestinian"], "-3.1 16.6 11.7": ["sprayings"], "8.5 30.0 23.9": ["swordfights"], "11.4 12.0 24.3": ["crocodilians"], "18.0 7.1 26.9": ["axolotl"], "1.8 7.8 11.0": ["jm"], "1.6 10.4 10.9": ["framerates"], "3.3 7.6 5.7": ["beause"], "8.1 17.6 7.2": ["hangmen"], "-6.3 2.2 1.7": ["menorrhagia"], "12.4 3.9 25.4": ["topknot"], "-0.9 -2.8 9.5": ["afterparties"], "8.0 28.6 17.5": ["elven"], "12.5 5.8 10.8": ["parklike"], "5.2 -10.6 6.4": ["py"], "12.8 2.4 2.2": ["deskside"], "-4.3 2.8 18.2": ["lim"], "12.0 9.1 3.8": ["traipses"], "5.8 12.4 8.3": ["digitalis"], "3.6 13.0 10.1": ["encodings"], "-1.4 5.0 18.2": ["oceanview"], "-4.2 -5.3 21.2": ["weaner"], "2.2 21.4 20.9": ["overmix"], "-0.6 15.8 3.3": ["misconfiguration"], "0.4 0.4 15.1": ["earlybird"], "5.7 0.3 10.3": ["bimodal"], "-0.5 9.3 3.1": ["stirringly"], "7.0 18.8 14.0": ["overzealously"], "7.8 12.7 13.7": ["unaffordability"], "2.2 6.6 2.7": ["squirreling"], "11.8 18.6 11.0": ["greyness"], "3.9 7.3 5.6": ["twinjet"], "22.3 -2.5 12.8": ["boobed"], "8.4 17.3 3.4": ["thirsted"], "27.7 27.4 23.4": ["minotaur"], "10.5 9.6 11.3": ["duchy"], "-6.7 6.4 8.4": ["retainage"], "-1.5 11.5 8.4": ["occipital"], "0.3 9.7 2.3": ["logout"], "6.3 4.0 13.1": ["contempo"], "1.1 12.8 14.3": ["makable"], "3.7 14.2 9.1": ["firies"], "3.0 18.5 5.0": ["sidedly"], "8.6 2.1 13.4": ["restocks"], "13.0 3.2 2.4": ["ouput"], "2.3 9.1 8.7": ["chronographs"], "3.7 9.8 6.8": ["cameraperson"], "0.5 14.2 14.5": ["sappiness"], "-8.4 11.8 -2.3": ["etat"], "-2.1 11.1 5.8": ["attemps"], "1.9 4.9 4.0": ["muraglitazar"], "-1.5 15.8 0.9": ["defensed"], "10.4 5.4 22.1": ["waterski"], "0.5 20.5 10.1": ["coms"], "1.9 6.2 -3.7": ["viscoelastic"], "-0.6 11.0 10.1": ["biopesticides"], "4.5 4.5 4.6": ["portuguese"], "4.2 10.8 11.6": ["competitivity"], "15.4 -4.6 1.4": ["okaying"], "5.6 15.6 11.1": ["lackadaisically"], "2.7 -2.5 14.6": ["neurontin"], "2.2 5.7 15.9": ["pinstriping"], "-2.4 7.7 6.5": ["bytecode"], "9.5 11.2 10.4": ["ghostbusters"], "0.3 1.8 4.3": ["listserve"], "9.1 5.6 5.0": ["batshit"], "-2.1 2.5 9.9": ["fallowed"], "19.4 12.5 18.9": ["ectoplasm"], "10.1 5.7 7.9": ["cleansweep"], "16.5 -6.8 5.6": ["mulit"], "5.8 -4.7 5.8": ["positve"], "7.0 4.5 -2.1": ["unpublicised"], "0.6 0.2 -1.2": ["improvment"], "-6.5 6.8 11.4": ["imiquimod"], "9.4 -7.9 5.1": ["roh"], "11.1 4.3 11.8": ["manhattan"], "-1.8 -4.3 -1.2": ["pexelizumab"], "16.6 12.3 12.8": ["piteous"], "-4.0 2.9 1.5": ["perineal"], "0.5 9.5 14.7": ["delimiting"], "13.1 18.8 13.5": ["bedroll"], "3.4 6.4 9.7": ["phosphatase"], "9.1 6.7 7.8": ["disappointedly"], "-2.8 7.8 3.4": ["sext"], "1.5 2.7 16.5": ["ww"], "-5.5 4.3 2.9": ["waivered"], "4.6 8.6 10.1": ["backchat"], "-3.4 8.8 38.6": ["shearwaters"], "1.9 4.6 9.2": ["orthography"], "-2.4 0.2 3.9": ["antiviolence"], "9.7 1.0 2.7": ["cinderella"], "11.0 6.0 14.3": ["unicyclists"], "2.0 6.9 -6.8": ["criticial"], "12.8 -1.9 15.9": ["woodcrafts"], "-2.7 5.1 -0.8": ["biopower"], "6.6 7.8 21.2": ["flava"], "6.0 3.3 11.9": ["aortas"], "15.5 15.8 2.6": ["immolated"], "-6.5 9.3 7.6": ["thiamin"], "-3.1 4.2 2.0": ["ofthis"], "2.8 7.7 7.2": ["unvisited"], "5.1 12.2 19.0": ["birdy"], "4.5 -1.6 -3.3": ["internationale"], "8.5 27.9 9.8": ["hypocracy"], "6.8 18.2 8.9": ["propitiate"], "9.2 10.1 10.5": ["scrunches"], "-2.4 -16.8 -0.7": ["oneyear"], "3.9 8.5 4.9": ["regadenoson"], "8.9 4.4 13.9": ["kn"], "12.8 19.4 8.7": ["legionnaire"], "7.6 8.6 6.4": ["feminised"], "15.8 12.2 16.3": ["beardy"], "6.9 18.4 14.8": ["temporality"], "17.6 9.0 17.8": ["girdled"], "-1.2 28.5 8.7": ["insomuch"], "-0.3 2.1 -2.8": ["guidlines"], "1.8 8.8 7.2": ["booklovers"], "2.4 7.9 9.8": ["antiprotons"], "0.1 1.8 11.3": ["missioner"], "10.0 4.7 14.2": ["clipart"], "16.0 9.0 9.4": ["schlubs"], "0.0 5.5 6.1": ["vomitting"], "16.8 11.0 12.5": ["skitters"], "1.3 1.7 13.4": ["chevy"], "7.2 22.2 7.8": ["consciousnesses"], "-3.9 7.7 4.8": ["foreseeability"], "2.0 13.6 6.3": ["loafed"], "-8.0 5.7 13.1": ["luthiers"], "-6.9 10.2 12.3": ["whakapapa"], "-0.1 8.9 20.6": ["snowshoer"], "-7.0 9.3 6.8": ["nonveterans"], "9.4 11.9 7.6": ["kitbag"], "5.1 6.3 9.3": ["tyramine"], "5.2 8.4 11.4": ["cleanable"], "-7.7 6.3 4.3": ["hypomagnesemia"], "4.1 16.2 19.5": ["raingear"], "-7.3 4.5 9.8": ["enduros"], "9.6 12.9 3.8": ["vill"], "3.3 11.5 11.5": ["mami"], "7.8 1.5 3.5": ["profesional"], "-2.5 7.4 7.4": ["urate"], "-3.0 8.6 16.4": ["overvotes"], "4.5 5.7 12.1": ["havelis"], "1.9 1.6 8.6": ["reupholstering"], "6.8 20.5 10.8": ["stubborness"], "-2.7 4.9 5.2": ["microcode"], "7.6 2.3 14.5": ["strapper"], "5.5 12.5 7.8": ["dawdles"], "6.9 -1.0 7.4": ["jw"], "8.5 2.9 7.8": ["hinky"], "9.5 12.4 10.3": ["cannoning", "lke"], "4.8 7.1 13.6": ["attheraces"], "-2.3 7.9 5.6": ["monophonic"], "1.4 -1.0 2.3": ["ampoule"], "5.1 7.6 12.7": ["fibronectin"], "7.4 8.7 14.0": ["conceptualism"], "3.2 3.7 9.5": ["hdl"], "-7.3 11.1 7.9": ["firstborns"], "-0.4 11.1 11.9": ["housetrained"], "9.9 6.1 28.4": ["agates"], "-1.7 6.8 9.8": ["lal"], "12.6 9.1 5.6": ["photoshopping"], "13.5 12.9 15.8": ["levelers"], "10.3 15.1 19.3": ["scouser"], "17.3 12.1 13.2": ["bidness"], "3.9 4.6 4.7": ["labeler"], "-7.4 4.3 4.0": ["reemployed"], "1.9 1.2 7.6": ["polypeptides"], "-6.9 4.2 15.9": ["mintages"], "0.9 22.7 5.6": ["vectoring"], "7.7 10.7 8.2": ["rondo"], "13.2 6.8 9.7": ["roughhewn"], "0.2 16.5 13.4": ["vunerable"], "3.5 11.8 7.5": ["bff"], "1.5 8.4 -0.1": ["renumbering"], "7.0 -3.0 8.8": ["pricetags"], "14.0 20.1 21.4": ["amidships"], "-5.4 1.0 2.2": ["adjudicative"], "-12.0 2.2 7.9": ["physiatrist"], "7.5 4.5 31.8": ["brulee"], "-1.0 9.0 4.5": ["bilinguals"], "-2.8 11.6 12.9": ["communicants"], "3.4 6.8 8.8": ["pricepoint"], "2.6 6.1 0.5": ["undresses"], "12.7 11.5 11.8": ["hallucinates"], "3.9 33.7 11.9": ["chickenhawks"], "-3.3 -9.9 6.7": ["colloquia"], "5.4 9.1 45.8": ["bowhead"], "9.2 5.7 19.0": ["sou"], "12.6 7.2 20.6": ["skylarks"], "-7.9 8.8 10.3": ["shojo"], "6.1 25.9 7.1": ["shapeshifter"], "1.3 7.6 3.0": ["ual"], "1.0 20.4 16.0": ["griefs"], "6.5 1.4 14.5": ["maison"], "13.5 7.3 25.8": ["amphora"], "11.3 11.0 31.3": ["agapanthus"], "6.4 9.9 17.4": ["lbws"], "3.0 11.4 2.4": ["bovvered"], "-10.2 -2.1 8.1": ["assistantship"], "-1.5 4.2 28.3": ["skimboarding"], "8.6 1.9 7.7": ["spoofy"], "1.2 -1.5 1.5": ["availablity"], "15.4 19.4 10.7": ["disemboweling"], "21.0 -0.1 4.6": ["emporia"], "7.5 8.6 7.4": ["petrolhead"], "7.0 4.3 7.8": ["fuelperks"], "7.5 10.6 2.7": ["sidestreet"], "-3.6 9.6 -9.2": ["reponsibility"], "6.1 9.9 -2.9": ["buttonholing"], "-5.7 6.7 2.6": ["mercaptan"], "14.0 6.0 2.2": ["goldmines"], "9.3 -2.6 19.4": ["creameries"], "3.5 16.1 7.3": ["incomprehensibility"], "6.9 11.9 9.5": ["fightbacks"], "-2.5 9.5 5.7": ["gastrin"], "-6.4 2.8 1.1": ["retiming"], "6.7 20.7 10.6": ["psychotically"], "2.0 4.3 9.6": ["recondite"], "14.3 4.3 7.9": ["slobbered"], "-3.2 -5.7 12.0": ["kanyang"], "6.2 11.0 18.3": ["flybridge"], "-3.1 0.5 4.0": ["distict"], "20.8 12.9 9.7": ["tailfins"], "11.9 8.8 23.3": ["peahen"], "-4.8 0.4 4.7": ["fluoropolymer"], "3.1 7.1 19.4": ["wop"], "9.9 19.3 33.4": ["bromeliad"], "-2.1 -7.8 -0.2": ["bioanalysis"], "-1.3 5.0 3.9": ["batchmates"], "8.2 11.1 19.6": ["flagellum"], "16.0 16.7 7.1": ["craniums"], "5.3 7.0 12.1": ["anodised"], "25.5 8.1 20.3": ["taxidermied"], "7.7 -0.7 25.4": ["blinis"], "5.1 14.1 13.0": ["pragmatics"], "-2.9 4.4 1.3": ["alloying"], "-1.2 11.0 7.8": ["chordoma"], "10.6 5.4 9.5": ["snappily"], "13.6 5.4 20.2": ["whorl"], "6.3 -1.9 2.0": ["bk"], "13.6 8.4 0.7": ["combusting"], "-3.8 -0.6 -3.3": ["oxymorphone"], "11.8 2.4 21.2": ["mao"], "4.8 -2.7 10.0": ["cabinetmakers"], "2.9 3.3 8.7": ["decamps"], "7.3 8.6 15.3": ["boma"], "2.2 -1.1 2.8": ["vida"], "0.7 11.6 12.0": ["vetiver"], "9.5 6.3 5.1": ["doorframes"], "1.0 8.7 9.3": ["ergometer"], "6.4 8.7 12.4": ["miley"], "2.1 15.8 6.8": ["mindedly"], "18.0 12.6 2.0": ["bionics"], "4.9 5.9 6.4": ["zipcode"], "3.0 28.3 9.1": ["detestation"], "2.8 4.8 15.4": ["downtowners"], "1.0 23.0 9.9": ["checkdowns"], "-2.7 16.2 31.7": ["furbearers"], "4.0 -5.5 13.3": ["oleochemical"], "2.9 10.3 8.8": ["messi"], "9.6 11.6 -0.5": ["smoulders"], "4.4 14.8 7.7": ["singularities"], "4.3 9.8 11.0": ["syncopations"], "9.5 6.1 14.4": ["crotched"], "5.3 4.1 -5.4": ["multimodality"], "5.1 15.7 27.6": ["allium"], "-1.3 13.0 4.6": ["subheadings"], "14.8 9.5 34.4": ["chimichanga"], "11.5 17.2 4.4": ["shitstorm"], "12.6 23.2 8.3": ["wickedest"], "29.3 8.7 -1.1": ["hightech"], "-2.1 3.1 14.9": ["bawdiness"], "4.1 11.5 7.2": ["peregrinations"], "14.9 14.6 19.9": ["shovelware"], "8.5 10.4 15.4": ["knuckleheaded"], "-5.2 6.9 3.8": ["geodatabase"], "5.2 8.4 15.0": ["showiness"], "3.8 -0.4 13.6": ["renos"], "-3.0 4.5 5.0": ["timeous"], "-6.5 14.0 0.4": ["nonelected"], "-3.1 13.7 1.3": ["nonideological"], "7.2 2.9 35.3": ["consomme"], "8.0 -4.4 2.7": ["prefilled"], "-1.4 2.9 7.9": ["mroe"], "28.1 24.7 20.5": ["planetoid"], "2.7 1.7 7.1": ["bazedoxifene"], "8.9 14.6 8.7": ["shithole"], "3.6 2.6 4.9": ["anemometers"], "8.4 17.0 5.2": ["marauded"], "4.9 -1.0 5.1": ["offcials"], "2.2 0.8 6.9": ["gerontologists"], "22.5 11.4 17.1": ["shrivelling"], "3.1 10.2 8.4": ["dismayingly"], "12.3 6.3 10.3": ["toroidal"], "7.1 20.8 6.5": ["millenarian"], "7.7 4.4 18.6": ["decadently"], "-4.6 14.9 -1.1": ["expellees"], "-4.4 16.7 -1.6": ["avows"], "1.9 21.4 6.5": ["realest"], "-0.5 13.7 7.8": ["deltoid"], "5.8 1.4 19.8": ["texturally"], "8.8 14.6 17.5": ["spraypaint"], "9.6 8.9 22.8": ["snowdrop"], "-12.1 10.8 6.4": ["achiness"], "-9.4 5.4 12.3": ["rav"], "20.0 -2.1 10.8": ["recyling"], "-9.8 0.4 1.8": ["fondaparinux"], "1.1 11.9 6.6": ["shabbiness"], "2.5 6.8 -1.1": ["degress"], "-6.4 12.9 -0.1": ["concretize"], "1.2 23.9 2.5": ["proselytization"], "5.4 -2.7 7.1": ["agriscience"], "9.4 4.1 13.5": ["proggy"], "-7.6 7.9 9.2": ["thoracotomy"], "12.4 6.3 10.4": ["playfields"], "17.0 24.1 11.7": ["decapitates"], "4.4 5.9 20.6": ["cadaveric"], "20.2 4.6 3.6": ["foldaway"], "3.9 2.8 13.9": ["kentucky"], "2.7 12.0 9.8": ["pamphleteer"], "5.1 12.0 13.9": ["swamis"], "6.4 8.5 4.0": ["grito"], "10.1 6.0 4.2": ["magnificient"], "-12.0 8.6 6.5": ["succinylcholine"], "10.2 9.0 9.8": ["pretentions"], "5.3 8.8 12.6": ["fanfic"], "4.8 8.6 10.8": ["gasified"], "-1.6 37.4 10.9": ["artillerymen"], "2.3 7.3 11.4": ["tulsi"], "8.2 10.1 6.6": ["borate"], "-1.1 7.0 0.5": ["overactivity"], "9.3 21.9 9.7": ["boobirds"], "6.1 5.6 13.8": ["brewmasters"], "0.9 2.7 3.1": ["febit"], "1.4 -0.2 -0.7": ["writeups"], "16.9 6.4 21.8": ["scoopers"], "9.5 7.3 -0.8": ["froing"], "12.7 25.9 9.7": ["conscienceless"], "6.2 5.2 1.2": ["uma"], "15.5 7.5 13.7": ["kool"], "7.5 -2.5 12.0": ["teethers"], "6.8 24.6 29.8": ["mealybugs"], "-1.0 9.7 11.0": ["reburying"], "-5.0 18.0 20.1": ["coveys"], "5.5 11.3 1.6": ["balancers"], "9.7 22.4 16.4": ["fleshly"], "4.9 -0.1 9.7": ["collarless"], "4.9 2.9 32.9": ["pozole"], "3.3 8.9 6.1": ["graben"], "-7.0 3.9 2.3": ["immunomodulators"], "-1.8 4.5 15.7": ["reverbs"], "6.7 10.0 13.3": ["radially"], "0.3 -3.2 0.3": ["adalat"], "9.8 13.7 7.7": ["asocial"], "1.2 0.9 7.8": ["aso"], "4.5 12.9 6.1": ["conciousness"], "5.6 13.2 21.4": ["kala"], "9.5 2.3 8.1": ["cassocks"], "-1.4 7.4 6.9": ["cytosol"], "8.4 8.3 27.3": ["piecrust"], "3.5 17.2 15.4": ["bodychecks"], "-5.1 5.0 3.6": ["semicolons"], "13.7 15.1 -0.9": ["defaces"], "1.9 25.9 3.7": ["estrange"], "-5.9 12.3 9.7": ["basebands"], "7.1 0.3 4.8": ["unattractiveness"], "-4.5 7.2 3.1": ["seaosn"], "-5.7 6.8 8.8": ["avulsion"], "0.0 4.5 12.4": ["microencapsulation"], "10.0 12.4 9.5": ["moviedom"], "29.2 -0.7 2.6": ["whizkid"], "2.0 13.1 0.3": ["galvanises"], "-4.3 16.9 1.7": ["internee"], "2.6 15.2 13.2": ["chillout"], "5.6 -4.7 4.5": ["appl"], "2.8 6.2 0.6": ["reposes"], "12.6 -0.7 18.0": ["ranchero"], "7.3 7.1 0.7": ["garrote"], "3.2 9.0 8.7": ["prostones"], "3.5 7.5 8.5": ["plasmonics"], "-3.4 0.0 3.3": ["ense"], "-0.2 8.7 9.3": ["theyd"], "15.1 18.4 6.0": ["gamemakers"], "-6.2 8.9 14.3": ["gritter"], "7.4 2.1 12.7": ["tuques"], "0.0 14.4 7.9": ["overacted"], "6.9 10.1 20.5": ["trishaw"], "5.3 8.6 23.7": ["oxbow"], "6.3 -0.8 14.6": ["todd"], "7.2 3.0 21.6": ["cummerbunds"], "3.5 6.9 12.6": ["boyishness"], "7.8 -3.5 4.6": ["ohs"], "1.4 14.4 1.8": ["legitimisation"], "4.7 5.5 8.6": ["ocrelizumab"], "10.2 3.7 19.0": ["northland"], "7.8 13.3 20.9": ["coniferous"], "-0.7 -1.4 20.1": ["pinker"], "8.1 11.7 7.9": ["askin"], "3.6 22.2 10.8": ["vietnam"], "7.1 23.0 3.6": ["stategy"], "3.6 3.3 8.6": ["meebo"], "4.9 3.7 10.1": ["amar"], "-4.4 3.8 20.0": ["sherries"], "0.9 9.3 7.5": ["havan"], "0.3 14.3 23.5": ["gamecocks"], "3.3 8.6 1.4": ["hydroxide"], "-5.3 9.7 -5.3": ["edified"], "6.3 14.1 -0.9": ["backseats"], "-0.0 30.0 5.1": ["brutalizes"], "-0.8 5.1 -4.2": ["loadable"], "3.8 4.5 6.3": ["itinerants"], "-6.1 4.5 14.2": ["channelization"], "7.1 16.3 3.2": ["semfinal"], "11.5 8.5 12.3": ["hissy"], "-3.8 -4.8 15.0": ["partials"], "10.0 11.3 4.9": ["radiometer"], "-5.3 3.0 0.5": ["degarelix"], "-4.7 0.2 2.6": ["marksheet"], "-7.9 -1.4 6.6": ["assistantships"], "-7.9 8.6 2.6": ["detenues"], "9.2 1.9 10.3": ["hehehe"], "4.9 12.5 3.5": ["incandescence"], "5.5 14.6 7.5": ["rationalisations"], "23.8 9.8 10.4": ["telecos"], "5.1 1.8 6.0": ["skimpiest"], "23.8 7.7 15.0": ["tailfin"], "12.8 6.4 25.1": ["carolina"], "3.9 11.0 18.2": ["kat"], "12.9 19.9 13.2": ["avoiders"], "-12.3 7.1 9.4": ["subgrade"], "6.2 2.2 13.0": ["ethnology"], "1.4 12.0 8.2": ["scintillometer"], "7.8 5.1 27.1": ["tanginess"], "1.7 6.0 4.2": ["ezines"], "6.9 14.2 6.7": ["jumpiness"], "2.0 10.5 7.2": ["chuppah", "stagework"], "4.3 16.9 10.3": ["plebeians"], "-0.5 7.0 -3.9": ["handwrite"], "-2.5 9.0 7.1": ["prebate"], "8.6 12.0 17.6": ["pastis"], "8.8 8.3 4.4": ["underexploited"], "3.4 1.9 10.9": ["jsa"], "3.6 14.0 2.8": ["bootrom"], "9.9 3.7 64.0": ["butterfish"], "-0.8 17.0 2.8": ["invalided"], "8.0 14.9 18.5": ["hookworms"], "8.1 16.0 5.5": ["haloes"], "0.7 6.9 18.7": ["wholegrains"], "9.1 5.5 9.6": ["cloyingly"], "2.2 5.3 12.9": ["yielder"], "-1.5 7.0 1.4": ["bogied"], "7.4 4.8 9.3": ["wher"], "2.8 2.9 18.5": ["elastics"], "1.6 8.7 4.2": ["governer"], "3.1 2.3 11.9": ["rego"], "-3.5 16.1 6.0": ["sura"], "1.2 12.6 1.0": ["seperates"], "11.0 6.1 13.2": ["sculptress"], "2.3 10.7 10.1": ["workless"], "2.8 16.4 0.9": ["internalizes"], "10.5 1.9 9.1": ["scavenges"], "1.0 2.6 25.5": ["coprolites"], "8.9 18.0 6.6": ["choppered"], "-0.2 34.2 4.3": ["psyops"], "8.1 30.7 20.8": ["overworld"], "1.7 1.5 3.0": ["axitinib"], "9.4 -1.6 19.4": ["mocktail"], "20.9 -0.9 10.5": ["didgeridoos"], "11.7 8.3 18.7": ["spittin"], "5.6 6.5 6.5": ["demergers"], "2.9 0.2 7.9": ["restripe"], "5.7 2.2 1.2": ["backround"], "2.3 -1.3 -6.1": ["transferral"], "0.3 13.2 11.7": ["litmus"], "4.9 11.1 9.6": ["weightiness"], "-4.4 9.8 6.3": ["qualifers"], "9.8 0.4 14.8": ["tuppence"], "5.1 4.0 11.8": ["groaners"], "1.5 12.8 15.6": ["tac"], "15.5 16.2 6.4": ["giantkilling"], "12.7 17.4 3.8": ["navigations"], "8.0 1.5 7.2": ["unfranked"], "11.7 14.2 2.4": ["consumerisation"], "-5.6 28.2 14.0": ["factious"], "-1.0 11.5 14.3": ["flyweights"], "1.7 3.6 14.7": ["sulfite"], "1.2 16.7 8.2": ["odorants"], "-6.7 16.7 1.1": ["inadmissable"], "10.9 12.2 28.1": ["tenderized"], "7.4 6.7 27.8": ["snorkeler"], "17.9 9.4 34.5": ["trawlermen"], "10.0 3.7 5.6": ["firsthalf"], "8.9 -0.6 -1.9": ["digitalize"], "13.0 11.9 -2.3": ["modernises"], "-1.0 3.9 4.4": ["transsexualism"], "5.7 17.9 6.9": ["deferentially"], "19.0 25.1 15.5": ["shapeshifting"], "18.4 1.0 10.4": ["bosomy"], "10.3 16.4 9.1": ["prudery"], "9.0 3.9 12.0": ["expresso"], "5.1 13.6 11.7": ["earworms"], "2.7 10.2 11.1": ["benchwarmers"], "-3.3 15.3 13.5": ["pasturelands"], "-13.1 12.2 20.2": ["inoculum"], "6.6 6.8 12.0": ["lekker"], "10.1 6.8 17.9": ["eveything"], "14.0 9.4 11.1": ["litterbug"], "15.1 4.3 8.6": ["deodorizers"], "9.5 8.5 2.7": ["leasers"], "1.8 4.6 14.1": ["commemoratives"], "5.5 -1.1 12.1": ["cappers"], "-0.9 -3.1 4.9": ["restriped"], "4.9 4.7 10.3": ["buildouts"], "-4.8 8.6 3.1": ["fibrate"], "1.4 11.2 4.3": ["subcellular"], "-7.1 19.9 5.3": ["contradistinction"], "-6.2 7.5 8.6": ["overclocks"], "8.8 12.2 13.9": ["blotto"], "0.1 9.9 10.2": ["typologies"], "-3.7 5.7 2.6": ["abbreviating"], "4.6 12.2 28.6": ["bitterns"], "-0.8 5.8 1.9": ["sensitiveness"], "0.7 16.9 3.8": ["illuminators"], "6.2 1.6 9.1": ["sep"], "-0.5 29.7 9.0": ["hearer"], "2.5 4.2 7.5": ["curent"], "9.2 15.6 3.2": ["againts"], "0.9 4.6 -4.3": ["adament"], "16.6 5.2 23.6": ["tickler"], "8.8 7.9 33.0": ["skippy"], "5.7 10.6 21.7": ["paylines"], "9.2 9.4 15.9": ["lectin"], "3.9 2.2 9.8": ["clearway"], "8.7 -0.8 26.8": ["crunchier"], "3.6 -1.3 12.9": ["tapos"], "-3.5 5.3 -4.2": ["remonstrations"], "12.0 -2.4 24.4": ["oatcakes"], "-2.3 7.8 4.8": ["distractibility"], "7.2 12.7 5.6": ["eta"], "6.0 17.1 10.5": ["sarkar"], "7.3 7.3 12.3": ["mumsy"], "9.3 12.5 26.0": ["disentanglement"], "-6.4 0.4 6.7": ["recertifying"], "7.4 16.0 6.6": ["symbolical"], "4.7 30.7 10.5": ["collectivists"], "8.5 4.9 12.7": ["flairs"], "20.3 4.0 15.1": ["riffic"], "10.8 10.4 2.4": ["browsable"], "2.5 3.3 21.2": ["marl"], "-0.2 1.0 -2.6": ["gategroup"], "6.3 2.5 7.9": ["cid"], "12.6 7.3 18.3": ["bucketfuls"], "8.1 1.7 24.8": ["mediterranean"], "4.2 7.4 20.0": ["diked"], "12.1 11.4 10.2": ["upskirt"], "13.2 0.9 8.5": ["toniest"], "4.1 10.2 3.2": ["stateswoman"], "5.3 -1.9 3.5": ["microfibre"], "-2.3 8.4 12.4": ["terai"], "1.1 2.7 -3.7": ["implead"], "5.4 7.6 7.3": ["owlish"], "14.8 12.6 30.2": ["lightship"], "7.7 4.6 26.8": ["boysenberry"], "-9.4 3.5 6.2": ["scorebooks"], "1.0 7.3 3.4": ["coprocessors"], "21.2 19.0 11.2": ["akimbo"], "-0.7 8.4 15.3": ["dewormed"], "18.6 24.3 13.2": ["replicants"], "18.2 12.9 14.9": ["parallelogram"], "3.1 9.3 -2.4": ["pple"], "12.0 3.5 9.6": ["ets"], "9.2 6.3 3.1": ["uproars"], "11.4 14.8 6.5": ["trypanosomiasis"], "11.2 4.5 8.3": ["wellas"], "22.6 9.0 -1.4": ["hoaxed"], "5.6 8.3 23.6": ["paddleboarding"], "9.7 16.6 9.0": ["mendicants"], "14.5 3.5 17.8": ["docker"], "9.5 0.1 11.5": ["suntans"], "10.8 -0.3 2.5": ["insitutions"], "13.1 5.8 5.2": ["cobwebbed"], "11.4 7.6 16.6": ["riverfronts"], "5.6 -3.5 2.8": ["janvier"], "-7.0 13.3 13.8": ["procrastinates"], "5.7 24.7 -4.6": ["revolutionists"], "7.9 3.5 12.9": ["sharpeners"], "-8.6 8.5 -1.2": ["verifiability"], "12.8 10.3 5.7": ["landesbanks"], "15.3 9.8 6.6": ["cruciform"], "4.0 5.0 5.5": ["bimah"], "7.0 10.9 12.1": ["vales"], "0.8 0.6 2.1": ["intiatives"], "19.6 2.5 15.5": ["dilly"], "7.4 -8.4 6.2": ["vers"], "-8.1 13.1 3.7": ["reconstructionist"], "-4.4 -5.0 9.8": ["requirments"], "10.7 8.1 16.7": ["guidettes"], "9.8 16.4 11.6": ["headcase"], "8.8 4.9 4.2": ["dekko"], "6.9 0.4 11.9": ["fortysomethings"], "17.2 10.4 14.2": ["whirligigs"], "5.4 7.1 3.9": ["venturi"], "-2.2 1.7 2.5": ["fulfiled"], "8.1 13.5 6.3": ["rossoneri"], "8.2 18.3 13.7": ["inevitabilities"], "8.6 9.1 10.6": ["stickies"], "-0.2 1.4 -2.0": ["cardiometabolic"], "8.4 3.5 8.6": ["flipflops"], "-2.0 1.3 3.8": ["premenstrual"], "8.8 29.0 11.9": ["necromancer"], "-1.8 6.4 8.8": ["unitised"], "6.5 23.1 10.1": ["refighting"], "-8.4 8.4 8.4": ["demyelination"], "5.5 19.7 -0.3": ["railwaymen"], "4.9 18.5 11.0": ["godfatherism"], "7.8 10.2 12.0": ["reanalyze"], "2.6 -2.5 9.4": ["remaing"], "3.8 9.4 1.4": ["buyable"], "2.2 12.5 2.6": ["depoliticized"], "-2.6 8.6 7.6": ["expectorant"], "2.9 15.3 12.3": ["neva"], "13.9 14.7 27.9": ["cottonmouth"], "10.4 4.5 15.5": ["gingko"], "-0.9 7.7 4.3": ["philanthropically"], "-4.8 -3.7 7.9": ["paraeducators"], "-2.0 16.6 2.5": ["obtainment"], "4.7 9.5 15.7": ["totepool"], "12.2 12.3 21.3": ["pooper"], "-5.3 0.5 18.0": ["farrow"], "8.6 2.4 13.4": ["axels"], "6.7 11.6 17.3": ["spurge"], "-1.4 10.6 8.7": ["khap"], "10.2 9.3 1.7": ["tricolors"], "14.0 10.8 14.2": ["buncha"], "9.5 0.8 9.7": ["ical"], "2.1 4.2 39.7": ["gremolata"], "16.9 4.7 17.2": ["scrollwork"], "11.9 3.2 8.3": ["prefigure"], "11.7 2.0 10.2": ["oklahoma"], "5.9 4.7 11.5": ["kana"], "5.6 12.7 14.0": ["spherules"], "1.0 2.8 25.7": ["carryouts"], "8.2 -7.9 11.0": ["septuplets"], "7.6 14.6 12.6": ["frigidity"], "8.0 29.1 8.8": ["blindsides"], "3.9 4.6 -1.9": ["prevalently"], "-3.7 3.8 6.3": ["receving"], "5.6 8.4 0.9": ["privelege"], "2.7 6.1 12.0": ["vermicompost"], "10.1 9.1 4.5": ["semiotic"], "2.0 13.0 6.5": ["hammerings"], "12.9 0.1 -1.0": ["laywers"], "13.0 10.2 10.7": ["hazily"], "4.7 9.0 2.3": ["insource"], "5.7 10.8 21.3": ["gastronomically"], "2.6 12.8 13.0": ["quoth"], "-1.5 8.0 31.2": ["tabouli"], "11.2 1.5 10.9": ["mtv"], "20.3 11.2 39.1": ["pumpkinseed"], "10.4 7.2 -5.4": ["quotients"], "5.4 1.0 9.8": ["tailpiece"], "9.5 8.5 7.9": ["subdirectory"], "30.3 10.5 13.2": ["doohickey"], "5.1 -1.3 10.0": ["multiclient"], "0.7 -1.5 2.1": ["microfilms"], "7.9 1.8 9.9": ["laminations"], "8.3 -1.5 8.7": ["aussi"], "-4.2 4.4 2.3": ["telepic"], "18.9 6.3 21.4": ["oscars"], "5.3 9.2 12.0": ["pasteurisation"], "-3.1 5.1 8.3": ["quitline"], "16.4 3.1 15.3": ["boxful"], "-4.3 5.6 9.6": ["footpegs"], "-4.7 6.3 1.8": ["pesantren"], "6.1 7.7 12.3": ["foglamps"], "4.7 12.6 9.0": ["secedes"], "3.6 5.1 10.9": ["biorhythms"], "4.2 9.7 12.5": ["euthanizes"], "2.1 2.3 7.3": ["productization"], "5.8 -5.5 0.1": ["kitemark"], "2.4 21.8 7.9": ["ingame"], "-7.4 12.8 3.6": ["testamentary"], "14.2 5.3 20.4": ["pigpen"], "16.3 12.1 10.9": ["grumpiest"], "6.0 7.2 10.0": ["seein"], "20.1 22.1 5.3": ["dominators"], "5.2 13.7 4.9": ["lockeroom"], "14.3 1.1 1.5": ["prodco"], "-0.1 7.2 12.2": ["peopling"], "13.2 10.8 5.6": ["doodler"], "-10.7 7.9 13.2": ["rainfed"], "11.9 12.3 26.5": ["falafels"], "8.5 15.2 30.3": ["hickories"], "-9.7 6.5 -4.7": ["experiance"], "-2.2 3.8 13.1": ["diyan"], "0.7 1.3 -4.9": ["classifiable"], "2.5 6.7 3.5": ["encapsulant"], "3.0 8.6 11.9": ["naam"], "22.8 4.7 15.2": ["megabuck"], "7.5 6.5 0.8": ["americium"], "-1.4 12.8 8.4": ["silents"], "3.6 4.2 7.9": ["primatologists"], "0.1 12.7 2.0": ["gossipers"], "12.3 5.9 7.6": ["bolshie"], "6.1 15.0 10.2": ["patronizingly"], "-2.4 9.3 12.3": ["quaver"], "5.4 11.2 12.2": ["netiquette"], "5.7 26.2 -0.9": ["blasphemies"], "0.0 7.4 3.1": ["statics"], "14.7 8.5 16.3": ["lumberman"], "12.0 2.8 3.9": ["analogized"], "-2.8 7.2 4.0": ["misidentifications"], "-1.9 15.0 4.1": ["topographically"], "-7.2 3.4 2.7": ["mirtazapine"], "-11.2 9.6 10.2": ["intermarriages"], "4.4 12.7 2.3": ["ghettoised"], "-0.5 15.4 7.1": ["idealistically"], "8.6 4.5 39.3": ["spoonbills"], "1.5 3.8 8.7": ["screencasts"], "5.8 13.8 14.3": ["lopsidedly"], "21.3 6.8 10.5": ["conks"], "-7.6 0.8 8.3": ["potencies"], "4.3 6.9 11.8": ["ipecac"], "14.6 19.2 15.2": ["armdrag"], "3.4 8.0 7.3": ["afaqs"], "13.6 12.2 20.5": ["hackberry"], "11.7 1.9 14.2": ["downunder"], "4.7 7.5 16.2": ["orleans"], "-7.7 1.2 -8.8": ["adressed"], "12.8 5.3 13.8": ["promenading"], "-2.2 3.8 17.4": ["brix"], "11.3 3.5 12.2": ["bol"], "-3.0 12.8 3.4": ["seliciclib"], "8.1 13.6 9.9": ["barcelona"], "7.7 9.8 19.0": ["edward"], "6.2 7.0 9.5": ["merchanting"], "5.4 13.2 7.4": ["dunnit"], "-2.2 9.3 4.2": ["precis"], "8.5 5.0 6.2": ["sangomas"], "13.4 4.9 6.2": ["blubbing"], "6.0 13.7 30.6": ["longshore"], "15.1 9.7 17.2": ["rasslin"], "7.1 16.1 14.1": ["dropsies"], "19.8 27.1 0.1": ["gestapo"], "2.6 6.0 23.3": ["crossbreeds"], "-1.6 3.5 10.8": ["screwcaps"], "7.5 4.4 9.6": ["gestate"], "17.0 9.2 6.5": ["paedo"], "-0.1 5.0 10.7": ["marraige"], "1.5 27.1 6.6": ["simplicities"], "19.2 1.0 13.7": ["capering"], "13.7 33.7 8.4": ["baddy"], "1.6 4.3 8.1": ["ple"], "-6.5 4.0 -1.6": ["uncontactable"], "2.3 10.1 0.3": ["canonizing"], "1.1 5.5 1.1": ["alkyl"], "0.0 5.3 3.8": ["marginalia"], "8.6 10.9 32.9": ["panino"], "-2.4 0.3 -3.4": ["testifed"], "-0.5 7.1 4.6": ["deselection"], "-4.1 9.6 6.4": ["intellectualized"], "12.8 11.5 27.2": ["thrasher"], "4.0 6.7 11.6": ["handycam"], "7.9 10.6 6.7": ["lexicons"], "5.3 5.4 3.4": ["midrise"], "15.1 15.1 -0.4": ["satnavs"], "1.9 18.6 9.2": ["latters"], "2.9 8.0 11.6": ["racegoer"], "9.9 -4.2 3.2": ["pizzaz"], "9.2 15.0 10.6": ["homescreens"], "11.9 19.3 -4.2": ["bankroller"], "-6.2 6.3 13.5": ["hsi"], "9.9 6.9 19.3": ["penstemon"], "2.2 0.4 12.7": ["vernissage"], "15.0 30.0 12.3": ["desolated"], "3.4 7.9 -0.3": ["recapitulates"], "11.9 8.5 -6.7": ["remanufacturer"], "-3.3 7.5 3.6": ["imbibes"], "-0.2 6.7 9.0": ["antifungals"], "4.3 12.0 29.7": ["snorkellers"], "4.7 -1.4 3.9": ["telent"], "10.5 11.4 32.9": ["lapwing"], "10.0 4.9 15.7": ["jackhammering"], "3.6 5.8 -0.5": ["kisan"], "13.8 7.4 26.9": ["hermaphroditic"], "7.6 5.3 15.7": ["shortcourse"], "-4.8 15.7 16.8": ["snowbelt"], "3.3 4.0 12.6": ["jrr"], "2.5 10.5 7.7": ["hoarsely"], "18.0 10.6 13.9": ["rosey"], "-1.0 -0.4 6.0": ["cial"], "2.6 11.8 14.7": ["whitelists"], "11.7 1.8 18.7": ["tio"], "0.2 13.0 5.3": ["poignance"], "4.1 -13.6 -0.8": ["inlcude"], "9.5 28.0 0.9": ["rocketeers"], "4.9 17.8 12.6": ["nostrum"], "14.9 3.9 18.6": ["maned"], "7.2 1.4 13.7": ["wale"], "12.6 10.9 26.7": ["boogaloo"], "13.1 -10.2 -5.0": ["annnounced"], "10.5 6.2 32.4": ["capsicums"], "-4.2 9.3 -0.0": ["readdressing"], "1.9 11.7 2.2": ["unachieved"], "9.6 7.2 9.4": ["hmmmmm"], "6.5 8.8 36.4": ["vichyssoise"], "2.6 -1.6 11.0": ["viatical"], "16.5 4.4 31.0": ["whalebone"], "10.0 20.7 16.5": ["enzuigiri"], "7.7 6.9 10.9": ["chawls"], "5.3 6.0 8.0": ["gasify"], "13.7 5.3 3.9": ["freshener"], "9.0 7.6 3.1": ["coziest"], "17.0 4.6 12.7": ["swilled"], "-0.7 8.8 16.9": ["peaty"], "1.0 9.1 9.6": ["kuti"], "5.7 12.4 13.2": ["dirtbike"], "9.1 1.8 5.7": ["upholstering"], "4.5 11.8 3.7": ["satanism"], "3.4 -4.3 10.2": ["verso"], "-3.0 14.1 2.5": ["goalers"], "-6.1 -5.6 6.0": ["expressor"], "5.7 -0.1 1.3": ["cyclodextrin"], "14.2 9.4 9.6": ["maharajah"], "10.4 -1.3 22.2": ["chien"], "15.7 1.2 7.2": ["spiffier"], "-5.5 18.7 -3.0": ["discreditable"], "0.2 16.5 5.0": ["unemotionally"], "5.9 14.6 6.8": ["neckerchief"], "-9.0 5.4 -2.8": ["neurogenic"], "-1.4 20.6 4.8": ["safehaven"], "12.4 9.2 7.4": ["clave"], "-4.8 3.7 -5.7": ["networkable"], "9.6 8.0 -0.6": ["reenergizing"], "-7.2 10.5 6.0": ["affectingly"], "12.4 5.1 15.8": ["demimonde"], "7.3 9.1 10.4": ["babys"], "2.7 23.5 10.3": ["depopulating"], "16.9 13.4 36.6": ["pufferfish"], "-5.8 4.9 7.3": ["estriol"], "7.6 4.8 32.6": ["raclette"], "13.4 7.5 2.1": ["brutalist"], "5.9 -0.1 8.3": ["hse"], "8.5 11.8 18.6": ["chillwave"], "4.8 8.6 3.7": ["urself"], "7.0 13.1 10.0": ["arbitraging"], "0.9 6.6 5.5": ["capsular"], "12.5 18.6 23.2": ["amoebae"], "5.1 8.1 9.1": ["thermogenic"], "-2.7 -7.8 5.0": ["shuh"], "0.1 9.7 12.4": ["overexpress"], "6.7 9.8 17.0": ["godmothers"], "11.0 9.6 32.9": ["petrel"], "7.9 19.1 9.8": ["doorkeeper"], "8.5 5.6 32.6": ["wagyu"], "18.8 0.5 41.6": ["croquette"], "0.9 3.0 10.9": ["nh"], "-4.3 3.5 32.9": ["russets"], "13.7 0.9 8.3": ["anteing"], "13.0 12.0 -2.4": ["spinned"], "0.5 7.8 10.5": ["tearjerkers"], "3.3 3.4 -3.2": ["biosensing"], "2.4 0.6 3.2": ["dass"], "14.4 10.3 36.9": ["weedless"], "12.6 22.1 9.5": ["hideousness"], "0.9 19.7 6.8": ["pointblank"], "-15.6 -4.6 -0.4": ["cesareans"], "-7.2 -0.1 3.9": ["determing"], "-1.1 6.1 9.2": ["anglicised"], "3.4 10.1 -2.7": ["presidental"], "13.2 9.7 7.7": ["meridia"], "-6.9 2.0 11.2": ["relaxers"], "8.0 16.3 9.0": ["pastapadre"], "-2.3 8.4 9.7": ["liftoffs"], "16.9 6.1 7.1": ["redissemination"], "18.2 9.1 9.3": ["unpayable"], "9.6 7.7 11.0": ["angstrom"], "4.3 5.7 10.7": ["ellen"], "7.6 30.5 0.9": ["mohareb"], "2.0 2.9 9.4": ["etudes"], "-3.1 6.9 4.9": ["valacyclovir"], "1.4 10.2 9.2": ["garnishee"], "2.8 25.9 3.0": ["anarchical"], "-2.0 8.8 9.5": ["claudication"], "15.6 15.2 16.6": ["odiferous"], "14.8 13.4 20.1": ["bearskin"], "7.4 -2.9 5.1": ["metallized"], "2.7 9.6 33.3": ["coldwater"], "2.7 4.9 19.2": ["comfrey"], "0.7 10.4 21.0": ["paperwhites"], "-2.5 -1.5 8.0": ["superscalar"], "2.3 12.7 10.2": ["avocations"], "5.7 9.7 3.8": ["intrusively"], "6.3 11.5 7.7": ["dizzied"], "4.7 13.7 2.8": ["riba"], "9.5 11.4 8.7": ["xy"], "-2.9 13.3 5.1": ["bipolarity"], "9.8 11.3 6.2": ["curvatures"], "4.4 16.3 25.2": ["caramelizing"], "2.0 6.7 6.4": ["paramyxovirus"], "16.5 14.4 31.1": ["seabeds"], "-1.0 10.2 3.6": ["hyperconnected"], "11.3 16.7 29.9": ["silverfish"], "-1.7 2.1 9.3": ["conferee"], "12.3 3.9 9.6": ["dayside"], "10.7 11.3 17.0": ["amakudari"], "-2.8 3.1 12.2": ["pandit"], "-7.3 -0.4 2.6": ["alvimopan"], "3.4 19.9 1.6": ["acuteness"], "1.8 16.7 4.8": ["positivist"], "3.5 6.0 28.4": ["kulfi"], "5.4 7.0 15.8": ["snowcats"], "4.0 1.2 13.3": ["parallelized"], "4.8 5.8 13.7": ["talkabout"], "3.1 9.4 7.0": ["militating"], "1.0 10.3 5.8": ["thumpings"], "19.9 2.8 6.6": ["secondquarter"], "-0.4 15.6 13.6": ["outdrive"], "13.6 26.3 7.8": ["scoffers"], "4.2 24.6 -1.3": ["fraternising"], "1.6 13.3 9.7": ["containments"], "5.7 13.7 21.8": ["forestay"], "24.3 8.1 28.3": ["churro"], "-1.7 5.0 7.3": ["motet"], "17.4 -1.6 4.4": ["biotechnical"], "-1.1 -7.4 -1.2": ["peformed"], "5.3 -5.3 -5.0": ["percentof"], "15.2 21.1 20.6": ["prickles"], "18.7 30.9 19.4": ["motherships"], "-7.7 12.0 5.4": ["lymphoid"], "0.1 5.4 7.2": ["equiv"], "20.1 10.5 15.2": ["dodgems"], "4.8 13.1 3.2": ["forsworn"], "7.9 5.9 26.7": ["gingered"], "8.9 5.1 9.6": ["stationwagon"], "7.1 14.4 9.0": ["bedchamber"], "10.4 -5.1 8.4": ["closedown"], "3.7 17.5 10.9": ["zamindar"], "12.6 10.5 45.2": ["yabbies"], "5.9 1.8 17.2": ["toney"], "3.7 20.4 6.4": ["altruist"], "1.5 14.4 13.3": ["wherefore"], "2.3 14.2 -1.0": ["effaced"], "1.2 5.4 10.9": ["kerala"], "1.9 23.9 5.9": ["backburn"], "-1.5 2.0 -0.7": ["aga"], "2.1 6.3 30.4": ["fisherfolks"], "0.7 21.2 15.5": ["rootworm"], "7.1 10.3 9.9": ["apexes"], "2.0 10.5 -1.4": ["elswhere"], "9.0 12.5 5.3": ["tearaways"], "13.1 2.1 -1.6": ["noticeboards"], "0.3 4.4 13.1": ["adjuvanted"], "5.1 13.5 8.7": ["catafalque"], "2.9 13.7 10.9": ["autochthonous"], "14.1 9.9 8.1": ["rugrats"], "24.3 8.7 17.9": ["bailer"], "0.1 7.8 0.1": ["handwash"], "4.5 10.5 14.8": ["quicklime"], "3.7 6.7 11.1": ["disinter"], "-5.9 4.8 4.8": ["wattages"], "-8.8 4.1 -1.5": ["subpart"], "8.3 7.6 -2.4": ["touchpanel"], "2.4 0.1 10.3": ["autocatalyst"], "11.4 21.6 5.8": ["streetfighter"], "3.2 1.2 6.7": ["parte"], "7.9 14.3 11.7": ["cubits"], "-4.4 4.1 12.8": ["syslog"], "2.7 27.9 3.5": ["nondemocratic"], "6.5 -6.2 15.6": ["basso"], "7.1 8.8 15.3": ["syncretic"], "2.6 -3.0 2.8": ["entreprenuers"], "15.1 18.5 6.8": ["bankster"], "12.9 15.2 7.8": ["oldfashioned"], "4.7 8.5 31.3": ["johnboat"], "1.0 8.0 14.6": ["ashfall"], "8.2 8.1 6.6": ["resodded"], "10.2 14.4 7.4": ["automagically"], "1.2 9.3 9.6": ["dopants"], "-0.3 -1.9 10.5": ["homier"], "-7.1 0.7 3.3": ["magicolor"], "5.7 3.8 12.6": ["printables"], "18.9 9.3 7.5": ["phobes"], "9.4 11.0 22.7": ["flatboat"], "16.6 11.8 12.7": ["monopoles"], "5.3 -8.5 8.8": ["ries"], "14.2 11.3 10.4": ["dunderheads"], "5.5 5.7 25.8": ["stonefruit"], "4.0 5.5 17.5": ["pizzo"], "7.0 12.7 5.2": ["goalfest"], "17.7 6.3 12.0": ["agrichemical"], "5.2 11.1 13.3": ["nofollow"], "19.0 10.6 32.0": ["chompers"], "10.6 3.3 6.3": ["weighbridges", "egy"], "11.6 11.3 8.5": ["burnin"], "0.3 21.0 13.3": ["uncomfortableness"], "2.7 2.4 8.1": ["deadpanning"], "4.7 10.9 3.2": ["compatibilities"], "0.8 9.9 6.0": ["skytrain"], "3.2 10.1 5.9": ["hellraising"], "-2.5 7.2 13.3": ["biotite"], "5.8 7.9 -2.5": ["trivialises"], "-6.0 -4.5 9.5": ["extendibility"], "-9.8 6.3 1.8": ["agreeableness"], "5.3 15.3 17.5": ["corniness"], "5.7 24.7 11.3": ["demonology"], "8.1 14.3 10.9": ["torturously"], "16.4 2.9 21.9": ["twink"], "0.1 12.5 5.1": ["undescribable"], "3.7 2.6 3.3": ["suncare"], "-1.3 9.3 12.9": ["coagulating"], "4.1 13.0 6.2": ["overprotected"], "4.6 15.1 4.0": ["untrustworthiness"], "-2.6 9.0 1.1": ["deprogramming"], "-5.5 9.2 6.7": ["loopback"], "-8.7 5.2 3.8": ["montelukast"], "1.2 10.9 2.8": ["missioners"], "8.5 6.0 9.1": ["blocos", "staan"], "7.1 11.9 8.3": ["camerawoman"], "12.9 11.5 15.9": ["oldster"], "7.1 10.5 7.8": ["savable"], "-8.7 2.1 2.6": ["atherectomy"], "14.1 -5.0 5.1": ["stationer"], "4.6 -1.0 21.2": ["capesize"], "8.2 11.6 18.6": ["moonshining"], "7.0 -1.0 13.8": ["coifs"], "-5.1 4.3 1.0": ["rithmetic"], "-4.8 2.5 2.9": ["forseen"], "6.3 1.2 17.0": ["narrowboat"], "-0.4 3.1 2.7": ["wheelbases"], "-3.3 11.6 10.1": ["wma"], "16.3 4.8 17.8": ["alaska"], "5.2 14.3 9.9": ["jaywalker"], "1.9 9.2 2.5": ["reverberant"], "10.8 22.2 10.8": ["battleaxe"], "1.2 6.2 -2.2": ["unenhanced"], "9.7 13.4 8.7": ["bumblers"], "2.7 7.0 15.2": ["dystrophy"], "11.2 8.3 3.8": ["sextillion"], "-1.4 6.3 5.4": ["reorganizational"], "10.5 13.7 -4.0": ["videoclip"], "0.4 16.7 8.7": ["attunement"], "1.8 20.5 32.8": ["loosestrife"], "2.1 -2.2 18.3": ["cheongsam"], "6.5 9.3 11.9": ["sista"], "-5.8 10.0 7.8": ["gharana"], "12.3 6.6 16.5": ["railbirds"], "14.4 18.8 7.1": ["uncoil"], "3.3 9.6 10.5": ["blowoff"], "2.6 -2.1 -1.1": ["dispell"], "12.8 15.6 3.0": ["halfwit"], "10.2 8.4 17.1": ["pinger"], "11.9 2.3 14.6": ["paisleys"], "12.8 4.6 4.8": ["hallelujahs"], "13.9 1.8 0.4": ["tantalised"], "-4.4 -3.7 3.4": ["semiautobiographical"], "9.1 22.4 11.7": ["changeling"], "-7.2 14.0 -6.3": ["inciteful"], "8.9 20.3 16.2": ["wog"], "11.3 3.2 35.1": ["ouncer"], "6.5 7.3 7.6": ["hobnobs"], "-2.2 2.8 -0.4": ["troubleshoots"], "5.9 9.2 4.7": ["interpolating"], "13.4 17.4 21.3": ["huntsmen"], "-3.2 14.0 5.8": ["catecholamines"], "3.9 17.4 10.7": ["stagflationary"], "-1.7 0.5 13.6": ["nilang"], "1.2 12.8 6.6": ["preachiness"], "2.2 5.9 7.0": ["bronchus"], "-3.0 20.5 0.1": ["indwelling"], "10.4 9.1 10.5": ["grotesquerie"], "-3.3 5.5 3.5": ["doa"], "-11.8 6.5 5.1": ["requestors"], "-7.1 5.4 2.4": ["threepointer"], "10.6 8.6 17.7": ["forelock"], "2.0 8.8 9.8": ["clusterin"], "2.1 5.4 12.6": ["kapag"], "9.5 -3.5 -5.0": ["assocation"], "0.7 19.5 1.1": ["tensest"], "7.8 4.1 -0.5": ["conducing"], "5.5 1.7 -3.5": ["lawfirm"], "16.9 8.5 9.8": ["japes"], "-1.8 9.7 8.9": ["footswitch"], "1.0 21.7 5.4": ["salvific"], "9.2 19.9 5.8": ["unmaking"], "2.4 -0.2 6.7": ["chinwag"], "-0.9 11.1 0.9": ["superintend"], "2.9 7.8 34.3": ["terrines"], "4.9 2.4 20.1": ["grom"], "0.3 -2.5 0.1": ["cosign"], "11.6 12.1 22.8": ["brewski"], "11.0 12.2 14.1": ["winkle"], "5.2 -0.1 4.4": ["weblinks"], "1.3 7.6 17.9": ["chino"], "1.4 12.2 5.6": ["camerlengo"], "7.8 11.0 9.4": ["squires"], "3.3 -1.5 4.5": ["togged"], "9.3 5.9 10.3": ["seachange"], "-4.2 13.9 9.9": ["deet"], "-5.3 26.4 6.8": ["unsparingly"], "2.9 13.6 29.9": ["trilliums"], "13.8 14.1 12.8": ["fantasises"], "-2.5 -0.4 8.6": ["gastroschisis"], "19.8 8.9 7.6": ["smelliest"], "6.6 6.8 5.7": ["widebodies"], "10.6 17.6 23.0": ["mycelium"], "2.3 5.2 13.6": ["bailey"], "0.1 14.7 14.2": ["desalinate"], "-1.8 16.6 -0.3": ["opporunity"], "1.9 7.5 4.9": ["impanel"], "-2.2 0.2 3.6": ["ideeli"], "4.9 5.3 10.2": ["transexual"], "15.5 16.4 6.9": ["helicoptering"], "12.0 5.6 0.2": ["surburban"], "-1.3 28.6 12.1": ["soldierly"], "-2.7 13.9 11.3": ["drollery"], "10.7 11.3 6.4": ["biddable"], "12.0 7.2 24.5": ["moko"], "1.6 11.8 50.0": ["tripletail"], "-4.8 2.1 4.8": ["proinflammatory"], "10.3 7.3 36.9": ["guillemots"], "4.4 10.1 2.5": ["anit"], "4.6 21.4 6.4": ["unredeemable"], "2.6 8.7 18.5": ["prunings"], "19.4 9.1 16.3": ["candelabrum"], "4.6 16.1 9.3": ["lacerate"], "3.1 12.1 13.1": ["amo"], "7.1 5.0 11.0": ["backbeats"], "8.6 26.6 2.0": ["penetrable"], "11.8 6.2 20.2": ["parkin"], "-2.0 -2.2 -3.1": ["saod"], "15.6 5.0 5.4": ["burb"], "8.9 0.0 11.6": ["elasticated"], "4.8 -0.5 16.9": ["fronton"], "11.9 7.2 3.7": ["syphoning"], "-4.5 8.2 8.3": ["findability"], "10.4 13.5 0.3": ["visable"], "8.1 18.4 11.2": ["insecticidal"], "0.9 6.8 -2.9": ["influencial"], "3.9 0.5 11.7": ["ower"], "2.1 23.0 13.4": ["queenside"], "-0.4 4.6 13.2": ["transferrin"], "-1.7 5.8 5.4": ["micropolitan"], "2.9 3.0 10.2": ["casegoods"], "9.3 10.8 0.9": ["unpractical"], "8.5 2.6 4.3": ["throughtout"], "1.5 10.4 16.8": ["dere"], "2.7 10.9 6.8": ["automatism"], "8.3 1.8 15.9": ["eddie"], "-3.9 10.4 5.4": ["undertreatment"], "9.4 4.6 9.3": ["prefering"], "5.1 17.9 19.4": ["cankers"], "-6.6 8.6 19.4": ["arnis"], "-1.9 16.6 7.3": ["windchills"], "4.4 8.0 14.4": ["defensman"], "7.8 5.9 10.3": ["ethereally"], "2.6 -3.1 12.2": ["riels"], "16.6 7.2 -1.4": ["rightsholder"], "16.5 9.2 0.8": ["superstation"], "13.4 22.0 7.7": ["unblinkingly"], "9.6 3.0 16.9": ["maca"], "23.3 8.5 -5.1": ["technolgy"], "15.1 8.2 9.3": ["pattering"], "1.8 19.8 4.8": ["worthily"], "11.1 31.4 13.3": ["gameworld"], "-8.6 1.1 1.9": ["veltuzumab"], "9.0 18.8 3.5": ["unpoliced"], "1.8 12.3 9.6": ["jwashington"], "13.8 12.5 13.2": ["scarpered", "snowshed"], "2.9 -1.0 11.2": ["orderable"], "-6.8 7.3 1.7": ["neuroradiology"], "-3.5 18.3 5.4": ["discriminator"], "3.9 2.4 9.8": ["standups"], "6.8 5.9 1.1": ["registrable"], "0.5 3.4 17.7": ["chippings"], "-0.7 -4.7 6.7": ["mtg"], "5.5 12.9 15.5": ["binky"], "0.9 20.9 6.3": ["highhanded"], "8.1 4.0 6.5": ["fobbing"], "13.7 12.4 13.6": ["girlies"], "-0.9 1.2 11.4": ["progestogen"], "5.0 10.2 2.7": ["maltose"], "-0.7 4.4 9.1": ["bookplate"], "11.5 4.1 5.9": ["plcs"], "-3.6 7.8 6.0": ["morbidities"], "10.0 8.6 8.4": ["singes"], "10.4 4.6 15.4": ["aaah"], "14.3 -1.2 17.1": ["tarball"], "-0.8 1.4 5.1": ["insulations"], "-0.2 7.0 2.1": ["occlusions"], "10.1 7.3 18.4": ["forelimb"], "11.7 15.0 1.1": ["imposingly"], "-0.2 5.0 7.0": ["duffels"], "13.0 16.2 11.7": ["favicon"], "4.6 10.9 9.5": ["usufruct"], "8.7 9.1 5.5": ["synchs"], "-5.4 20.8 -1.4": ["resposibility"], "-7.8 6.1 -3.4": ["critized"], "17.1 10.4 17.1": ["supercontinent"], "-3.6 19.0 8.1": ["salam"], "9.5 4.8 -3.0": ["permament"], "-0.9 1.0 16.4": ["castrati"], "10.1 13.9 10.6": ["invincibles"], "5.6 3.3 8.0": ["paycuts"], "17.7 7.1 11.0": ["euphorically"], "-2.8 7.8 12.5": ["swaybar"], "-1.4 9.1 4.9": ["bursted"], "5.6 -3.8 7.6": ["bolivares"], "11.1 8.9 12.4": ["krautrock"], "2.4 6.0 11.1": ["hydronic"], "-3.3 15.6 12.6": ["pederasty"], "0.6 9.6 3.6": ["hairsplitting"], "-5.0 10.2 10.6": ["morphologic"], "-10.5 -0.1 5.2": ["homebirth"], "17.7 3.4 10.8": ["mouldering"], "10.8 20.6 17.8": ["giftee"], "0.7 7.8 5.2": ["instantiated"], "3.1 6.3 12.4": ["oprah"], "4.2 2.2 6.2": ["hoc"], "-0.4 6.5 19.0": ["ungroomed"], "22.4 3.3 4.9": ["goldrush"], "15.7 8.6 6.9": ["mousepads"], "10.8 16.5 4.9": ["actuating"], "5.0 6.5 3.1": ["darapladib"], "14.5 3.8 -1.4": ["iniative"], "13.0 10.4 13.5": ["moobs"], "-0.4 4.1 3.3": ["pesewas"], "-12.2 6.5 6.9": ["remitters"], "12.8 9.3 13.0": ["melter"], "-7.3 4.9 0.9": ["nonsecure"], "-2.8 8.2 12.2": ["equipoise"], "0.9 30.6 6.7": ["armorer"], "10.3 -1.4 11.7": ["walkathons"], "-3.8 2.5 12.0": ["funniness"], "3.8 13.0 3.7": ["maintaing"], "-9.4 8.2 -4.8": ["arraigning"], "2.7 11.7 8.4": ["traumatically"], "5.2 3.3 7.5": ["stairlift"], "12.1 10.9 16.1": ["gaur"], "6.2 14.0 12.9": ["skiving"], "-8.6 5.0 -2.0": ["levetiracetam"], "-8.7 6.7 4.2": ["nephrectomy"], "-3.8 12.9 10.1": ["anions"], "13.0 24.0 1.6": ["countermoves"], "11.6 6.8 0.4": ["underprice"], "12.7 7.0 28.5": ["lingonberries"], "4.0 8.0 2.9": ["agencywide"], "13.1 -5.2 10.7": ["kronur"], "3.4 8.8 1.3": ["nugatory"], "5.7 4.8 4.6": ["songstresses"], "11.3 10.3 -4.2": ["cloakrooms"], "9.9 13.2 9.1": ["frostier"], "11.4 6.9 12.2": ["museumgoers"], "-13.6 7.1 -2.8": ["controverted"], "-1.5 2.2 5.2": ["oxybenzone"], "8.1 15.0 12.0": ["pinkos"], "0.7 4.8 13.9": ["kaming"], "2.5 18.4 8.7": ["tediousness"], "-1.1 12.9 5.1": ["relatability"], "1.9 11.7 17.5": ["phosphorescence"], "10.9 3.5 16.2": ["sellin"], "13.3 1.6 2.5": ["reprographic"], "-1.6 1.6 7.0": ["digipack"], "5.0 10.7 6.5": ["unstained"], "3.3 13.1 5.6": ["cagily"], "4.4 10.7 10.2": ["fasters"], "5.6 22.7 6.4": ["debilitates"], "12.1 5.7 34.1": ["galette"], "-2.7 3.6 20.5": ["kamaaina"], "6.7 8.2 14.2": ["dognapping"], "8.3 10.1 7.5": ["umlaut"], "14.5 2.6 25.0": ["gummies"], "1.2 5.0 0.2": ["lightweighting"], "2.7 9.1 12.0": ["vibing"], "-1.3 19.2 5.4": ["retentive"], "-2.4 21.1 9.1": ["denuclearise"], "-5.4 13.1 0.1": ["dewpoint"], "-3.4 0.9 10.2": ["phys"], "16.1 11.7 14.1": ["neath"], "-0.8 4.0 9.4": ["uprating"], "1.1 5.7 10.2": ["dermabrasion"], "-0.7 32.3 9.0": ["pacifistic"], "10.3 20.0 17.2": ["holodeck"], "4.4 8.4 18.2": ["septics"], "0.3 7.4 16.2": ["phenology"], "17.4 14.0 7.5": ["arbitrageur"], "3.6 10.9 -1.9": ["turbofan"], "-3.0 8.6 23.0": ["gewurztraminer"], "8.1 2.7 22.9": ["morgan"], "6.2 -3.9 10.3": ["groundworks"], "-3.3 12.1 19.4": ["mainlander"], "2.0 13.2 15.0": ["centrefield"], "6.1 12.4 -0.6": ["jubilating"], "4.5 19.6 8.6": ["liberations"], "2.6 12.6 37.6": ["shellcrackers"], "-5.7 3.8 10.1": ["racewalk"], "-2.6 9.5 9.0": ["transshipped"], "3.1 5.4 30.8": ["briskets"], "9.7 3.3 5.1": ["petrophysical"], "3.5 17.7 15.5": ["sistership"], "-6.0 5.9 2.6": ["debentureholders"], "5.9 1.5 9.3": ["dockable"], "10.1 4.4 30.6": ["brill"], "2.0 1.1 8.7": ["preferment"], "-0.0 12.6 7.5": ["stratabound"], "-0.7 -0.4 0.8": ["conferenced"], "16.0 15.0 21.4": ["furries"], "5.2 18.5 18.4": ["deadeye"], "1.2 8.5 2.1": ["imporant"], "3.2 14.1 11.9": ["backlift"], "0.0 -4.1 8.4": ["biobanking"], "10.5 11.1 2.2": ["communed"], "1.2 13.0 4.0": ["langauge"], "0.4 23.2 0.5": ["intifadas"], "4.3 7.3 15.8": ["hagwon"], "9.3 9.6 19.6": ["prokaryotes"], "19.3 7.7 11.4": ["gaudiest"], "2.2 7.2 4.1": ["outlandishness"], "3.5 18.1 5.3": ["hatemongering"], "-4.2 11.2 5.1": ["quadrature"], "0.2 6.2 8.7": ["jcc"], "7.2 9.9 18.4": ["intermezzo"], "-6.5 5.9 -0.6": ["thnk"], "4.4 22.8 -1.4": ["overflown"], "-1.1 5.9 7.0": ["efflux"], "-1.2 -1.2 3.8": ["lectors"], "8.3 -1.7 7.4": ["highquality"], "3.8 0.0 -0.7": ["perfector"], "7.7 9.3 7.2": ["sailplane"], "1.3 7.1 32.4": ["mirin"], "7.4 13.9 16.7": ["sekiwake"], "7.4 9.6 7.6": ["evey"], "13.8 13.3 22.2": ["homonym"], "8.9 4.5 20.4": ["lank"], "10.0 7.7 10.3": ["chiropodist"], "13.0 6.6 1.5": ["consol"], "-5.1 -0.4 1.4": ["putamen"], "9.2 -7.4 5.3": ["amonth"], "22.5 12.9 18.7": ["quadruped"], "6.6 6.3 8.4": ["crankset"], "12.7 13.8 6.2": ["hypnotise"], "2.4 -1.1 31.3": ["ceviches"], "-3.0 40.0 6.5": ["counterinsurgencies"], "10.7 2.0 8.9": ["winelands"], "13.7 3.8 28.4": ["knishes"], "14.8 -3.6 7.8": ["relabel"], "5.4 5.3 -7.7": ["sevice"], "-3.3 2.4 5.6": ["epirubicin"], "13.3 6.2 10.7": ["pinballing"], "13.0 4.6 5.0": ["cheerio"], "1.3 7.5 11.7": ["crosscuts"], "12.8 8.7 27.9": ["caimans"], "15.6 -2.7 4.7": ["superhospital"], "1.7 24.2 6.7": ["hypervigilant"], "2.2 15.6 1.7": ["unretiring"], "0.5 11.9 11.5": ["extemporaneously"], "12.1 8.1 7.3": ["clouts"], "3.2 2.7 7.4": ["polarizers"], "-2.8 6.4 6.4": ["aflibercept"], "6.9 16.4 7.8": ["dourly"], "18.8 14.2 11.2": ["unscrambling"], "-2.9 1.5 4.4": ["verapamil"], "4.5 18.6 15.7": ["nonaggressive"], "-3.7 -1.8 0.0": ["redelivered"], "1.5 8.0 4.7": ["bucindolol"], "-0.5 15.4 -1.3": ["zindabad"], "9.3 5.5 2.5": ["neurobiologists"], "15.3 7.8 2.2": ["beholds"], "-4.2 14.5 16.4": ["replenishments"], "-1.3 3.2 -0.2": ["fastmobile"], "8.9 5.7 2.2": ["angstroms"], "9.7 5.9 15.6": ["unlaced"], "9.3 1.2 0.3": ["amalgamates"], "-5.3 9.5 6.3": ["runningbacks"], "10.1 12.5 3.9": ["anonymizing"], "0.5 2.2 16.6": ["lola"], "-1.2 6.3 9.2": ["unshowy"], "0.0 21.1 2.4": ["untiringly"], "14.5 19.3 21.6": ["hurricanrana"], "13.1 9.6 8.0": ["posterboy"], "-1.9 11.1 10.7": ["oversteering"], "1.9 15.4 15.4": ["onchocerciasis"], "-4.3 6.7 8.8": ["breaststrokers"], "2.1 8.3 3.0": ["zhahd"], "11.2 11.8 14.9": ["smithy"], "-4.6 9.1 12.6": ["mkg"], "2.2 -0.5 10.8": ["minumum"], "3.6 8.6 41.8": ["dashi"], "6.7 17.0 11.1": ["nawab"], "2.5 5.7 5.9": ["propos"], "2.7 -5.9 3.0": ["dicuss"], "2.8 15.6 5.1": ["prober"], "1.8 6.7 5.7": ["fringy"], "2.5 5.0 15.5": ["aff"], "2.8 7.9 10.7": ["discouragingly"], "-2.3 3.0 17.1": ["breaststrokes"], "-5.4 26.0 6.7": ["traumatizes"], "0.9 8.6 7.3": ["lysosome"], "5.8 4.6 2.4": ["afew"], "21.1 11.4 34.4": ["corndog"], "3.5 -5.6 5.4": ["reran"], "7.0 17.1 3.6": ["understatedly"], "-0.1 10.2 8.3": ["raxibacumab", "fiats"], "17.2 15.1 22.4": ["napper"], "8.4 11.4 8.2": ["westernisation"], "13.8 7.8 9.8": ["bedazzle"], "1.3 7.6 26.2": ["khichdi"], "1.0 4.1 14.6": ["sateen"], "6.2 6.1 -2.4": ["professionalising"], "11.1 8.0 7.5": ["glamazon"], "14.1 13.9 16.2": ["coquette"], "12.8 10.8 17.9": ["wetbacks"], "6.9 1.9 -3.6": ["wurde"], "13.1 5.6 4.0": ["carring"], "5.5 11.8 31.2": ["plowman"], "9.3 20.2 11.5": ["bravehearts"], "-2.0 5.7 9.8": ["monotonic"], "8.2 4.2 24.0": ["brekkie"], "0.3 4.5 -0.6": ["oximetry"], "6.9 13.8 8.8": ["crystalize"], "18.3 8.7 8.8": ["changeroom"], "18.1 0.6 20.1": ["tacular"], "3.8 3.9 13.6": ["bole"], "0.6 3.7 6.9": ["testier"], "-6.8 17.4 4.6": ["memorisation"], "11.6 25.3 12.5": ["manoeuvrs"], "-0.2 -4.5 4.6": ["metalsmithing"], "-3.1 -5.2 8.9": ["ams"], "16.2 8.6 18.4": ["braziers"], "21.2 9.5 9.0": ["skywriting"], "8.4 0.5 31.5": ["pau"], "-3.1 10.2 11.6": ["recitatives"], "3.9 5.2 4.6": ["themarket"], "4.3 9.8 15.6": ["shamisen"], "1.8 15.7 2.8": ["perjured"], "9.6 7.0 11.0": ["sino"], "-0.9 -0.3 3.6": ["reco"], "3.4 2.9 2.1": ["caravanners"], "7.7 12.4 8.8": ["womyn"], "12.4 0.7 9.1": ["tangoed"], "0.6 18.8 12.5": ["subjunctive"], "-3.4 0.9 5.8": ["panhandles"], "3.0 -2.5 -0.0": ["incentivises"], "6.2 9.1 7.9": ["budges"], "7.1 14.5 5.5": ["lineaments"], "-9.0 15.3 16.7": ["larviciding"], "13.9 3.0 16.2": ["luna"], "2.5 7.3 11.0": ["melodicism"], "21.7 11.9 11.3": ["oompah"], "2.2 6.8 8.9": ["hitmaking"], "5.9 13.1 12.4": ["fornicators"], "7.1 5.9 6.7": ["xo"], "-7.0 10.3 3.3": ["misapply"], "13.1 -0.5 5.2": ["highend"], "7.8 8.7 9.4": ["sutras"], "5.7 7.8 21.4": ["repotted"], "12.1 4.0 11.0": ["puli"], "7.2 5.5 13.1": ["unusal"], "10.2 14.6 3.0": ["beeing"], "13.7 16.9 8.4": ["credos"], "-2.1 1.0 15.2": ["rsum"], "8.3 2.9 3.0": ["compatibly"], "-6.9 3.3 1.4": ["winnning"], "-6.0 -6.7 5.4": ["reapproved"], "-3.6 13.8 6.0": ["deposes"], "0.2 6.1 3.8": ["pantoprazole"], "17.9 25.8 15.4": ["flamers"], "6.8 10.2 7.6": ["copyleft"], "5.6 16.8 -1.2": ["embracement"], "2.0 0.0 8.0": ["chumby"], "-6.2 6.7 2.7": ["serotonergic"], "2.6 6.7 2.6": ["concretised"], "4.2 13.0 13.9": ["shoegazer"], "3.6 12.8 12.1": ["crispest"], "5.3 4.6 12.3": ["speculum"], "-4.3 9.2 2.2": ["saquinavir"], "1.1 9.3 15.6": ["iyan"], "12.0 1.1 3.4": ["hydrocolloids"], "16.8 9.3 12.9": ["nightlights"], "4.8 0.1 10.0": ["franco"], "-0.0 7.4 11.2": ["flashflood"], "6.2 5.4 0.6": ["depite"], "6.4 10.4 16.7": ["microbiome"], "11.3 1.2 14.1": ["footbath"], "8.2 13.5 14.5": ["rascality"], "11.5 16.9 5.2": ["asshattery"], "5.3 7.6 17.1": ["sailmaker"], "7.6 17.0 38.6": ["downrigger"], "-10.9 8.3 7.1": ["hypothyroid"], "6.2 6.6 18.9": ["patisseries"], "-0.4 -1.7 15.9": ["kebaya"], "5.2 31.4 3.5": ["dehumanise"], "29.9 0.6 0.3": ["comany"], "5.3 7.9 7.8": ["leeds"], "6.6 12.0 15.4": ["trapezes"], "23.0 11.9 11.9": ["crookedly"], "4.0 8.6 8.8": ["placeshifting"], "-0.2 3.3 14.6": ["desexed"], "8.1 11.6 6.2": ["constructivism"], "11.7 4.9 11.8": ["chica"], "16.5 11.4 11.7": ["nimbus"], "7.6 -0.4 13.0": ["bulldogging"], "9.9 14.6 10.5": ["pardner"], "5.5 9.3 13.8": ["ead"], "16.8 2.3 17.7": ["moggies"], "1.2 14.1 5.9": ["reckonings"], "-7.1 18.5 7.2": ["originalists"], "16.5 6.1 16.9": ["poofs"], "13.0 3.9 25.5": ["limeade"], "4.5 6.1 6.6": ["abi"], "-7.1 -0.4 9.1": ["fers"], "-1.2 1.3 6.0": ["ders"], "7.8 13.5 6.2": ["pedlars"], "-1.8 9.3 5.3": ["ozarelix"], "11.8 17.3 16.3": ["suplexed"], "-1.1 11.1 7.3": ["infatuations"], "13.0 5.8 35.9": ["cornichons"], "6.2 3.6 23.1": ["suspender"], "4.3 10.0 12.1": ["wn", "rickbroida"], "3.9 13.8 13.9": ["chooser"], "1.1 9.8 20.8": ["apiaries"], "7.6 12.0 2.9": ["proprietorial"], "12.8 3.8 1.4": ["preinstall"], "7.1 16.0 5.1": ["unobservable"], "3.9 16.5 -11.0": ["misimpressions"], "2.7 7.3 9.0": ["hsun", "breviary"], "-3.5 9.6 4.2": ["downregulation"], "3.1 11.7 -3.2": ["pointsman"], "1.0 -4.2 -4.8": ["intrathecal"], "6.9 13.2 13.4": ["biomolecule"], "11.2 1.8 10.3": ["straightener"], "4.6 0.2 7.3": ["hangtag"], "-2.7 0.9 0.1": ["webiste"], "9.6 4.1 19.0": ["doobie"], "4.8 2.1 9.1": ["metropole"], "15.9 -4.1 4.3": ["crescendoed"], "4.7 1.7 13.1": ["ringgits"], "1.1 19.4 7.4": ["gruesomeness"], "-0.4 11.7 8.5": ["expectable"], "-5.5 0.8 13.7": ["inclusives"], "2.8 6.1 19.3": ["snoozers"], "2.0 8.9 6.3": ["disputatious"], "-3.5 8.7 4.2": ["dispatchable"], "3.8 -1.1 12.7": ["tala"], "4.2 2.7 2.5": ["gemology"], "-1.1 -3.5 15.3": ["fussier"], "15.1 9.7 15.5": ["beamers"], "4.1 8.7 8.7": ["chateaus"], "9.9 4.9 14.8": ["stromatolites"], "0.5 5.1 7.6": ["unitl"], "2.9 9.2 3.5": ["godmen"], "5.7 6.8 10.3": ["katrina"], "-1.1 12.7 11.2": ["tumorigenic"], "1.1 10.4 5.4": ["incantatory"], "13.5 5.8 36.1": ["tartlet"], "16.4 14.3 11.3": ["rubberneck"], "1.7 1.2 2.9": ["tsa"], "4.7 9.8 16.6": ["solstices"], "2.6 14.3 8.7": ["adminsitration"], "-3.2 2.9 -0.9": ["biodata"], "-1.3 14.4 5.4": ["policyowners"], "5.2 9.4 13.0": ["appreciators"], "14.1 14.3 17.9": ["patricians"], "0.5 8.6 13.2": ["kababayans"], "5.9 3.6 11.0": ["repointing"], "9.4 2.6 3.4": ["frequenter"], "8.8 4.1 2.3": ["bronchoscope"], "17.9 12.1 25.9": ["dormouse"], "4.2 11.0 -3.8": ["averring"], "6.3 4.8 5.2": ["shld"], "-13.2 5.6 5.3": ["neoadjuvant"], "10.1 7.3 5.5": ["microelectrodes"], "12.8 -7.3 -2.9": ["marka"], "7.1 10.8 3.4": ["decarbonise"], "7.4 6.4 11.5": ["apna"], "5.3 12.5 13.2": ["outguess"], "0.6 17.8 5.6": ["aliveness"], "16.3 7.0 33.0": ["fricassee"], "5.2 4.7 6.4": ["probaly"], "11.8 0.3 9.1": ["trollies"], "-6.9 8.8 5.9": ["namaaz"], "1.2 14.7 10.4": ["bacilli"], "7.9 -1.1 12.6": ["haggles"], "16.0 10.3 -2.6": ["counterdemonstration"], "12.3 5.2 3.1": ["drubs"], "-6.1 6.0 14.7": ["pasturing"], "3.8 0.9 0.3": ["nik"], "3.1 9.6 13.5": ["dashboarding"], "11.1 2.8 14.0": ["deja"], "4.7 13.1 21.6": ["brah"], "-0.1 8.9 3.6": ["amout"], "5.4 18.9 8.3": ["reparable"], "7.5 13.4 2.9": ["bastardisation"], "6.6 13.4 2.6": ["shakti"], "-0.1 12.8 2.2": ["nosocomial"], "1.0 12.1 11.2": ["mandibular"], "-5.8 4.9 2.4": ["sone"], "18.4 5.8 17.9": ["baobab"], "9.6 5.6 4.0": ["ident"], "6.5 3.7 2.5": ["decklid"], "0.9 10.2 1.1": ["concretise"], "15.5 11.8 12.4": ["antennagate"], "10.0 10.7 4.4": ["gulled"], "19.1 7.0 23.2": ["geodes"], "6.3 12.3 11.9": ["spottings"], "4.6 11.3 10.0": ["infirmaries"], "6.2 6.4 13.1": ["househusband"], "7.6 12.2 1.6": ["launders"], "7.3 13.3 7.8": ["garbs"], "11.4 6.0 13.3": ["coolstore"], "0.4 10.0 7.4": ["unmeritorious"], "0.9 14.6 13.5": ["nubber"], "3.5 1.7 17.5": ["shen"], "17.3 8.8 16.2": ["pollie"], "2.5 6.2 15.6": ["uncleaned"], "13.0 4.9 18.9": ["vivarium"], "9.2 5.7 24.5": ["chao"], "17.3 -1.1 9.2": ["hasta"], "-8.6 8.8 6.5": ["symptomatology"], "5.6 13.9 9.8": ["gutful"], "6.2 3.2 13.8": ["stroker"], "9.7 8.5 8.1": ["sia"], "2.4 5.1 6.8": ["nifedipine"], "10.4 12.3 5.3": ["cartelization"], "-4.0 11.7 11.8": ["overcurrent"], "5.4 9.4 13.5": ["castrato"], "0.9 5.1 53.8": ["gillnet"], "0.8 5.5 31.7": ["sofrito"], "-2.6 14.3 2.1": ["humoral"], "14.4 20.6 18.8": ["goobers"], "6.3 17.6 3.1": ["anarcho"], "0.7 8.9 14.3": ["itraconazole"], "-0.6 2.5 26.2": ["angus"], "10.8 -13.2 -0.8": ["propsed"], "0.3 9.8 7.1": ["storyboarded"], "-1.9 2.4 -6.4": ["serializing"], "26.6 25.4 20.6": ["flyswatter"], "6.9 18.2 23.6": ["pugmarks"], "7.2 9.1 19.4": ["hoi"], "-0.1 -0.5 11.2": ["ferrule"], "4.8 22.9 13.6": ["highwayman"], "9.8 3.5 20.5": ["chinoiserie"], "7.5 -11.5 6.4": ["yaer"], "12.7 8.1 4.7": ["verger"], "0.9 -0.9 6.5": ["cadetship"], "8.3 8.5 33.4": ["fisherwomen"], "23.6 7.9 12.9": ["draglines"], "2.6 11.4 8.7": ["actioners"], "9.8 2.7 12.4": ["drearier"], "1.4 1.2 4.2": ["reargue"], "-8.1 12.7 -2.2": ["accountably"], "6.3 2.9 12.8": ["gratingly"], "7.0 14.0 8.3": ["autorun"], "3.7 7.3 17.0": ["oxidization"], "-3.5 5.3 3.0": ["detoxed"], "6.4 22.4 4.1": ["denominators"], "3.3 6.7 13.7": ["kia"], "6.5 2.1 6.4": ["orlando"], "8.3 6.3 8.8": ["alongs"], "-1.9 5.1 6.7": ["upvalley"], "1.7 11.9 20.4": ["morphologically"], "9.1 4.4 6.7": ["thestate"], "13.8 12.2 12.4": ["moshpit"], "3.5 20.9 7.3": ["premodern"], "4.7 -0.9 6.6": ["doubler"], "10.5 12.6 24.5": ["foxgloves"], "2.1 25.9 15.6": ["kingside"], "11.1 6.6 6.7": ["pinyin"], "12.1 4.4 1.8": ["univ"], "-0.8 14.2 5.2": ["soundbytes"], "5.4 8.1 3.1": ["reductase"], "6.2 8.7 -5.6": ["unassociated"], "4.5 -7.1 3.5": ["prepays"], "-1.4 12.1 2.9": ["crosslinking"], "-2.3 1.6 4.6": ["lymphoedema"], "4.5 5.2 17.1": ["woolshed"], "15.6 11.7 11.1": ["resentfully"], "0.1 7.0 7.3": ["sweden"], "-0.6 7.4 11.0": ["pharmaceutically"], "21.3 9.3 25.8": ["stippled"], "-3.2 8.7 5.3": ["tradability"], "19.7 10.1 9.2": ["thwacked"], "12.9 11.0 15.5": ["weaseling"], "4.1 1.1 22.7": ["pysanky"], "19.6 7.1 23.2": ["constrictor"], "0.9 17.7 3.0": ["posess"], "11.0 14.3 1.0": ["catchcry"], "11.5 16.5 18.6": ["prickle"], "3.4 4.4 12.4": ["chronologies"], "7.2 10.7 10.4": ["scousers"], "2.8 -1.8 5.1": ["reroof"], "4.2 1.5 8.5": ["porsche"], "-18.0 11.9 3.9": ["nonadherence"], "7.7 11.7 4.3": ["clickstream"], "-5.1 1.0 3.1": ["authentications"], "-3.6 23.3 14.0": ["reenactor"], "5.6 5.9 33.1": ["saltmarsh"], "1.2 6.0 4.4": ["splaining"], "18.5 -6.3 17.2": ["cherrywood"], "12.2 24.7 7.9": ["unreasoning"], "2.7 1.1 6.1": ["js"], "7.9 4.4 32.3": ["shortcakes"], "5.3 22.1 1.2": ["expiate"], "1.4 9.3 20.8": ["viburnums"], "21.0 0.3 9.3": ["jingled"], "16.5 9.8 3.4": ["caricaturists"], "1.8 2.3 15.4": ["onsales"], "13.1 4.5 4.9": ["mundial"], "17.7 7.2 26.6": ["canape"], "15.9 9.9 11.4": ["thimbleful"], "-6.8 6.2 0.8": ["typescript"], "-2.9 14.4 4.1": ["linksters"], "20.4 17.4 17.8": ["skulled"], "7.6 -8.1 1.2": ["bizjournals"], "15.4 20.1 8.5": ["carpetbagging"], "-2.3 0.2 -0.1": ["baskeball"], "8.2 20.4 10.8": ["arseholes"], "4.1 5.1 3.7": ["swotting"], "4.4 -0.0 9.6": ["oftheir"], "-5.7 23.8 2.5": ["servanthood"], "-6.2 12.0 15.9": ["watercrafts"], "5.3 9.9 2.9": ["technophobic"], "12.9 24.1 5.5": ["unpiloted"], "9.6 13.7 23.0": ["slammers"], "19.0 8.2 11.4": ["crimewave"], "7.9 9.6 7.1": ["shoegazing"], "1.6 6.5 6.6": ["churchwarden"], "5.4 22.0 8.3": ["escalatory"], "6.5 29.7 16.1": ["meanly"], "5.0 7.2 11.9": ["carsick"], "0.4 5.5 2.3": ["regulary"], "-4.1 13.0 8.3": ["mawkishness"], "5.3 16.9 0.1": ["prescence"], "4.0 11.2 5.8": ["numerological"], "17.8 11.6 14.6": ["pushpin"], "-3.4 20.8 4.4": ["outworks"], "-1.2 16.4 9.1": ["centeredness"], "5.3 3.8 2.0": ["harmonises"], "12.0 -1.6 12.4": ["millworkers"], "9.9 12.4 4.4": ["purism"], "1.3 8.8 10.5": ["aramid"], "11.0 13.0 7.9": ["skedaddled"], "22.8 7.2 4.6": ["deathwatch"], "3.3 9.8 8.6": ["backordered", "macth"], "2.7 13.2 2.3": ["scaremonger"], "8.9 0.9 17.1": ["servery"], "9.2 10.3 3.9": ["unring"], "2.9 22.8 10.7": ["contrariness"], "5.4 -6.5 -1.6": ["accordingto"], "7.2 12.2 11.8": ["kopeks"], "10.0 13.2 14.3": ["congeals"], "2.8 7.1 7.1": ["metatarsals"], "8.0 9.2 5.8": ["emos"], "17.0 7.0 15.0": ["vitrine"], "3.5 12.7 10.4": ["upsurges"], "2.9 10.9 15.7": ["tpg"], "13.2 20.6 20.7": ["brainbuster"], "12.2 6.7 0.6": ["supercluster"], "-8.1 9.2 2.9": ["sentance"], "9.2 5.2 7.3": ["shhhh"], "21.1 16.6 28.9": ["spined"], "3.8 7.4 2.1": ["headhunt"], "-7.3 9.9 13.6": ["permittees"], "-5.7 2.8 10.7": ["postsurgical"], "-3.0 12.5 8.9": ["tenseness"], "5.1 5.2 8.4": ["shee"], "5.0 -5.8 4.2": ["payrise"], "1.8 9.9 7.7": ["nonscientists"], "9.0 12.2 9.8": ["frak"], "7.5 -3.0 12.9": ["fah"], "9.0 22.1 19.0": ["brits"], "-2.5 3.7 3.6": ["doorknock"], "16.5 4.7 5.6": ["rulemakers"], "0.8 1.0 13.5": ["racedays"], "0.1 5.1 14.4": ["bronzers"], "0.3 11.5 10.0": ["misbehaviors"], "14.7 -2.8 9.6": ["neons"], "2.8 -1.4 11.0": ["polocrosse"], "8.1 13.7 18.4": ["groaner"], "6.2 6.7 -0.7": ["successfuly"], "-7.3 -4.8 3.4": ["lookback"], "5.3 0.8 11.3": ["underpromise"], "-3.2 13.2 5.8": ["naturism"], "-1.2 10.9 9.5": ["tere"], "-0.7 7.9 4.3": ["detoxifies"], "-4.3 4.5 8.6": ["fms"], "28.0 16.0 10.5": ["thingamajig"], "3.1 3.6 9.2": ["oesophageal", "voiceglo"], "0.4 10.7 9.1": ["avery"], "-0.4 7.1 15.3": ["equivalencies"], "8.2 0.2 10.6": ["hiccupping"], "2.9 9.5 -0.3": ["campaing"], "21.0 6.6 15.2": ["maraca"], "3.0 7.6 10.5": ["jasperoid"], "3.9 7.4 19.2": ["packhouse"], "-9.7 3.1 10.2": ["tudung"], "11.1 13.8 9.4": ["firefighers"], "15.8 13.6 14.2": ["froyo"], "3.0 16.8 4.0": ["longsuffering"], "8.2 12.2 17.3": ["foolin"], "2.0 8.8 5.0": ["jetways"], "6.4 7.2 6.4": ["prattles"], "6.7 5.6 8.7": ["ince"], "20.8 16.3 12.1": ["levitates"], "-3.3 3.5 23.1": ["ugali"], "0.8 10.3 2.2": ["reinfected"], "-9.2 11.8 2.2": ["chemoprophylaxis"], "-0.3 3.6 6.8": ["plagiocephaly"], "17.8 18.3 12.0": ["boardgame"], "-0.9 14.1 8.0": ["dicamba"], "12.5 11.4 18.5": ["lapis"], "9.6 10.5 9.2": ["prankish"], "1.1 9.4 8.0": ["freeskiers"], "10.4 1.6 -0.1": ["proferred"], "6.3 18.1 12.7": ["loudhailer"], "1.4 12.3 4.3": ["bandsmen"], "10.5 1.6 12.1": ["toupees"], "-4.5 7.8 -2.8": ["untaken"], "16.7 7.7 5.0": ["prettified"], "9.5 -1.1 21.7": ["punnet"], "8.0 3.7 8.1": ["cumed"], "-0.9 1.8 10.9": ["juvenilia"], "10.0 10.4 8.0": ["workshy"], "-6.9 10.7 11.4": ["macrocell"], "2.3 10.2 7.9": ["beatmaker"], "-4.0 7.8 8.2": ["ponts"], "-0.9 6.8 7.4": ["soring"], "1.4 17.9 17.3": ["officemates"], "0.4 7.2 5.4": ["humidex"], "1.0 21.0 9.4": ["infallibly"], "1.8 -6.1 6.0": ["montly"], "5.7 11.3 9.2": ["bewail"], "3.6 9.3 18.2": ["fireblight"], "4.3 13.9 14.4": ["scarcest"], "-2.1 9.5 7.3": ["socioeconomically"], "23.0 14.2 17.0": ["cartoonlike"], "2.6 13.4 11.9": ["miskick"], "11.9 5.5 8.3": ["reregulation"], "-2.5 7.1 6.3": ["librettos"], "6.6 12.3 15.4": ["logline"], "6.7 4.4 13.4": ["cableway"], "0.6 4.1 5.8": ["enalapril"], "7.4 1.7 1.6": ["mismarked"], "-6.7 3.7 6.2": ["discretes"], "10.1 10.7 4.3": ["gladdens"], "5.3 9.7 5.4": ["prognosticated"], "-6.4 21.3 14.6": ["avoidant"], "-6.5 20.9 11.1": ["disjunctive"], "2.3 8.0 3.4": ["lengthily"], "11.2 2.2 27.8": ["huevos"], "-5.0 -2.2 5.3": ["externships"], "2.2 12.4 8.3": ["grammarian"], "-2.5 0.8 12.7": ["capitated"], "2.0 9.7 10.2": ["sacristan"], "4.2 1.9 19.4": ["caipirinhas"], "9.1 19.6 10.4": ["trickiness"], "1.4 10.5 6.3": ["electrosurgical"], "-2.0 21.6 13.2": ["lvl"], "-1.1 3.8 10.7": ["missouri"], "11.9 -0.7 14.8": ["ivi"], "7.2 3.0 6.0": ["secondhalf"], "15.9 20.5 0.9": ["reprograms"], "16.8 5.6 7.4": ["decadeslong"], "10.0 5.9 7.7": ["eminences"], "12.0 2.9 18.1": ["serval"], "13.0 8.1 9.3": ["arriviste"], "-2.9 1.6 9.5": ["nodular"], "0.2 25.7 3.1": ["sanctifies"], "4.0 4.5 7.4": ["mispronunciations"], "0.7 14.5 5.6": ["protract"], "15.1 9.0 10.6": ["strewed"], "-0.5 13.6 13.0": ["nurturance"], "2.5 7.8 4.7": ["viewability"], "18.7 13.0 10.8": ["ocarina"], "16.0 4.8 13.6": ["unicyclist"], "2.2 0.6 11.0": ["barebone"], "9.8 15.8 10.1": ["fondles"], "-3.8 -3.3 5.8": ["endodontics"], "0.1 17.9 1.2": ["fatwah"], "11.3 19.0 19.1": ["nunchaku"], "16.9 1.7 14.9": ["shabbier"], "8.8 12.3 0.9": ["theranostics"], "6.8 0.9 10.1": ["celebutantes"], "10.9 2.0 13.8": ["ste"], "-1.6 4.6 4.1": ["glyburide"], "3.0 13.4 3.3": ["fictionally"], "17.5 12.0 17.5": ["oilers"], "-2.9 3.9 11.3": ["dramaturgical"], "9.1 8.4 10.6": ["backboned"], "15.9 18.3 15.7": ["massiveness"], "3.9 10.1 8.5": ["statures"], "30.5 7.5 22.7": ["gumdrop"], "3.6 15.0 -2.2": ["germicidal"], "11.7 10.5 7.4": ["unprofitability"], "3.3 3.4 16.1": ["stewart"], "-1.0 13.8 1.2": ["misconstrues"], "-2.5 9.2 12.4": ["hosel"], "21.1 17.4 16.8": ["wolfish"], "8.0 10.4 11.8": ["eyepieces"], "1.0 13.1 7.2": ["whitespace"], "-3.9 4.6 7.5": ["catechin"], "8.4 0.1 36.6": ["asiago"], "-0.6 18.8 5.3": ["convoyed"], "-4.6 5.3 5.7": ["deicers"], "-3.9 13.7 3.1": ["personation"], "9.1 2.2 4.6": ["moring"], "-2.8 3.0 10.1": ["jatra"], "12.6 18.2 14.4": ["egotists"], "14.0 18.9 21.8": ["lodgepole"], "-0.6 6.2 -5.5": ["experince"], "-1.3 7.8 15.6": ["inebriates"], "5.9 13.6 15.7": ["greenscreen"], "6.8 1.9 6.6": ["rome"], "-0.7 0.4 8.7": ["glial"], "-2.1 14.7 3.6": ["keratitis"], "4.3 3.7 3.3": ["thie"], "-5.8 23.5 6.7": ["microbursts"], "-5.5 8.6 6.1": ["macroeconomists"], "0.4 2.8 2.2": ["talkshows"], "1.6 6.7 7.7": ["recessionista"], "6.9 7.3 8.3": ["thebe"], "12.5 6.6 24.9": ["tommy"], "-1.7 4.9 12.2": ["vocalese"], "17.2 8.0 12.6": ["tutting"], "4.8 5.5 2.0": ["adsorb"], "-4.1 19.1 8.4": ["madressahs"], "4.3 -0.1 -1.6": ["libelling"], "0.7 -1.4 16.2": ["naturalizations"], "5.1 24.6 7.8": ["embitter"], "15.7 11.1 10.6": ["doofuses"], "0.2 23.1 9.4": ["scarified"], "11.5 -0.9 15.3": ["babydoll"], "14.5 10.1 48.7": ["periwinkles"], "-8.7 9.4 6.4": ["recanvassing"], "-4.3 10.1 15.6": ["throttleman"], "16.2 12.4 11.3": ["wallah"], "10.0 17.4 6.8": ["hermetically"], "3.6 -0.6 5.3": ["thsi"], "16.8 17.9 19.5": ["pecker"], "1.1 1.8 1.8": ["almosts"], "-4.8 14.2 9.7": ["cenotaphs"], "10.8 11.5 27.6": ["gristly"], "-6.0 7.2 5.4": ["vv"], "11.3 10.0 6.4": ["stupefaction"], "-1.8 17.1 0.4": ["refueler"], "6.3 9.9 15.8": ["bobbly"], "0.4 11.5 -0.3": ["dif"], "1.7 8.8 7.3": ["ummmm"], "0.7 2.8 11.5": ["archa"], "-7.8 11.6 7.1": ["childproofing"], "1.3 -1.3 7.0": ["milemarker"], "2.1 10.5 8.2": ["collet"], "-1.4 5.2 6.2": ["horrorcore"], "1.4 3.5 5.3": ["pneumonitis"], "-2.5 25.1 5.8": ["evasively"], "5.5 4.1 22.3": ["unbaked"], "2.4 8.7 2.3": ["catchwords"], "20.0 26.5 7.7": ["pulverise"], "-1.9 5.9 6.1": ["teb"], "5.6 -4.4 8.9": ["contrabass"], "5.2 -3.0 12.4": ["peridot"], "1.3 5.7 1.6": ["intradermal"], "-1.5 27.8 7.0": ["maoist"], "12.0 7.2 12.4": ["woohoo"], "-0.6 8.6 1.3": ["jumpoff"], "-0.5 12.8 10.7": ["stippling"], "8.9 9.4 13.5": ["nuttin"], "7.6 11.6 21.3": ["kali"], "9.0 6.3 18.2": ["amla"], "9.5 18.8 9.5": ["pantheism"], "0.5 -3.7 3.6": ["inagural"], "10.0 7.8 13.4": ["orangery"], "2.0 7.7 5.2": ["scatty"], "3.5 7.6 9.5": ["clickthroughs"], "-3.0 8.1 5.3": ["starrers"], "0.9 18.7 14.5": ["infinitive"], "6.1 -1.6 14.4": ["latina"], "-9.5 6.2 3.0": ["antiemetic"], "17.4 10.6 4.8": ["untether"], "9.7 2.6 8.1": ["elasticized"], "2.0 5.4 20.2": ["brett"], "14.5 1.1 8.9": ["zamboni"], "9.6 12.6 22.0": ["hydrophone"], "10.9 7.2 4.6": ["ohne"], "16.6 3.4 11.7": ["towheaded"], "3.5 3.9 8.2": ["guernseys"], "7.4 25.3 9.8": ["providentially"], "-0.7 0.8 8.4": ["sufficent"], "10.0 14.1 14.9": ["baseplate"], "23.8 6.4 8.6": ["semitransparent"], "9.0 8.1 7.1": ["tanto"], "6.2 12.5 18.9": ["willie"], "-5.4 13.6 6.3": ["autoantibody"], "8.6 13.2 17.1": ["galpal"], "-5.7 3.9 1.5": ["deputises"], "-10.1 12.5 -1.2": ["renouncement"], "6.6 13.2 14.4": ["retie"], "-5.0 5.2 6.4": ["satsang"], "14.9 19.0 7.9": ["pamphleteers"], "15.5 20.2 11.2": ["kneecapped"], "12.4 13.8 21.2": ["pokers"], "9.8 14.0 8.5": ["exasperatingly"], "4.2 11.0 7.8": ["queerness"], "12.4 12.0 29.5": ["cycad"], "0.8 7.3 -5.0": ["cardioversion"], "5.3 -0.4 6.8": ["promotor"], "3.7 5.3 20.9": ["cenotes"], "-0.7 0.9 3.2": ["deferrable", "autres"], "11.3 15.7 35.3": ["tules"], "-7.1 0.1 11.7": ["trich"], "6.5 20.7 3.6": ["hyperbolically"], "-1.0 -5.1 6.9": ["discuses"], "17.4 9.7 29.7": ["constrictors"], "8.6 3.8 4.9": ["cowls"], "4.4 5.8 3.5": ["broadbase"], "11.1 5.0 7.0": ["nanogenerators"], "10.7 11.9 15.9": ["meadowlarks"], "-4.0 14.3 12.0": ["downmove"], "8.2 16.1 20.2": ["vulgaris"], "-1.4 5.3 12.1": ["vocalism"], "10.4 8.9 18.3": ["massa"], "9.3 -6.0 5.0": ["jetsetting"], "8.9 3.2 39.4": ["sandpiper"], "24.4 10.7 11.7": ["boxlike"], "2.9 12.8 9.6": ["itiveness"], "-8.3 5.6 16.7": ["pani"], "-3.0 4.2 7.5": ["playlets"], "-6.8 1.6 2.2": ["withdrawls"], "5.3 5.1 18.7": ["containerization"], "3.4 4.5 9.9": ["folkish"], "16.6 24.2 8.5": ["pitilessly"], "-4.0 14.0 8.4": ["labile"], "2.0 0.6 16.3": ["choosey"], "-2.6 4.5 6.7": ["atopic"], "21.1 5.2 14.4": ["flourescent"], "6.1 9.0 10.4": ["premiumisation"], "4.0 6.5 -0.2": ["multivariable"], "12.4 23.9 16.8": ["wussies"], "3.1 2.3 10.2": ["batched"], "14.3 12.4 7.5": ["scathed"], "-4.5 3.9 1.4": ["sangha"], "10.6 12.2 5.8": ["subfolder"], "0.8 11.7 19.6": ["animatic"], "10.2 29.8 14.4": ["knightly"], "-9.7 5.4 6.6": ["deductable"], "3.6 12.9 12.4": ["nonracial"], "-6.6 4.9 1.9": ["stavudine"], "-7.2 13.9 5.1": ["fictionalize"], "8.6 16.8 5.0": ["inseparably"], "7.4 4.9 2.6": ["consumate"], "-3.6 0.3 14.5": ["rehabbers"], "10.8 1.9 16.0": ["mousey"], "6.4 17.4 25.3": ["subarctic"], "2.0 12.6 3.9": ["beseeches"], "6.6 5.5 8.0": ["unembellished"], "16.4 -0.2 11.8": ["foodstore"], "4.0 1.7 27.7": ["kuih"], "-5.1 5.5 7.3": ["liturgist", "trackday"], "1.9 13.9 15.1": ["wakeskating"], "12.5 3.9 23.0": ["barrette"], "3.9 15.3 7.0": ["bearishly"], "0.4 7.5 3.1": ["superlatively"], "11.6 17.9 3.7": ["pictorially"], "-3.1 10.6 11.0": ["onlys"], "10.0 10.6 24.6": ["spongers"], "4.6 8.0 19.5": ["heatpipe"], "0.8 6.8 6.2": ["noseweek"], "7.4 5.7 13.3": ["ususally"], "10.3 15.2 9.2": ["refracts"], "3.1 14.7 4.6": ["gamebreaking"], "5.7 4.3 10.5": ["coatless"], "0.4 5.4 8.9": ["nonelderly"], "6.5 10.7 12.1": ["amyloids"], "8.2 -0.9 9.9": ["toing"], "-7.4 15.2 4.3": ["refoulement"], "-0.8 5.3 -1.2": ["unserviced"], "4.3 -0.2 4.9": ["unsuccesful"], "8.7 -2.4 11.6": ["giro"], "13.5 12.0 0.8": ["vigourously"], "-3.0 4.3 6.0": ["thymalfasin"], "6.3 6.6 11.0": ["gravelled"], "1.7 6.8 2.3": ["cricinfo"], "10.7 8.4 2.8": ["picketer"], "3.0 22.3 13.1": ["regicide"], "6.6 17.2 8.3": ["heliosheath"], "-0.6 3.8 13.3": ["premixes"], "-8.5 7.5 -0.2": ["capacitate"], "5.2 2.4 4.0": ["smh"], "1.6 1.8 -0.3": ["deemphasize"], "12.7 27.7 16.2": ["reapers"], "4.5 9.9 12.2": ["passivation"], "-0.8 0.2 0.3": ["acct"], "4.8 12.7 11.1": ["suitemate"], "0.2 24.7 7.4": ["perpetuators"], "13.4 16.1 16.5": ["dickheads"], "-2.4 16.4 3.2": ["strech"], "12.2 -3.8 5.4": ["ola"], "-6.1 3.4 5.1": ["linehaul"], "15.0 22.8 1.3": ["supersecret"], "-2.5 11.1 19.9": ["pilsners"], "9.4 8.2 3.4": ["blair"], "-5.4 11.3 -4.9": ["redlines"], "0.3 14.6 3.4": ["perseverence"], "7.4 14.3 8.4": ["inexpedient"], "-3.4 1.8 0.5": ["overprescribed"], "-2.2 3.1 1.0": ["spottier"], "4.8 9.1 1.9": ["xxxxx"], "5.5 3.3 14.6": ["musica"], "-1.5 7.0 17.3": ["statebreds"], "9.0 15.4 9.5": ["exciton"], "6.0 10.6 6.2": ["metrological"], "1.4 14.4 10.4": ["sallies"], "-3.5 3.1 0.3": ["transdisciplinary"], "11.7 4.5 16.9": ["shanzhai"], "8.7 9.3 10.2": ["cuttin"], "11.3 11.7 18.9": ["zippo"], "0.3 -3.8 5.4": ["hree"], "0.3 8.2 10.0": ["corridos"], "6.6 8.4 13.4": ["neuropeptides"], "0.7 7.7 51.9": ["coastwide"], "0.2 4.1 -0.4": ["runned"], "6.1 8.8 8.8": ["uncrowned"], "1.0 -4.5 9.0": ["wovens"], "2.6 15.1 2.2": ["bjp"], "3.6 10.9 1.4": ["teetotaling"], "3.4 10.7 7.1": ["kimberlitic"], "9.7 3.1 4.0": ["baseballer"], "15.0 6.2 12.7": ["bonnie"], "-3.0 5.6 12.7": ["ima"], "13.9 13.3 16.2": ["stolidly"], "10.0 11.5 7.5": ["hostnames"], "-9.0 5.7 9.2": ["prorating"], "4.4 7.0 -0.5": ["aber"], "-3.3 -0.2 0.7": ["temazepam"], "10.0 1.8 1.0": ["higest"], "24.0 7.4 6.7": ["swooshed"], "5.7 2.1 12.7": ["becquerel"], "11.1 10.5 29.7": ["macaron"], "4.5 8.8 6.1": ["dopant"], "6.4 4.7 -0.4": ["editorializes"], "6.8 2.0 9.1": ["ners"], "9.4 21.9 14.9": ["oughtta"], "10.1 8.3 5.3": ["traffick"], "15.1 14.5 14.5": ["lickin"], "-6.0 2.7 6.1": ["wpm"], "6.4 2.8 5.4": ["vlogging"], "-7.3 -1.9 17.1": ["soyfoods"], "-10.0 9.6 7.3": ["overtrained"], "7.2 5.6 8.3": ["hughes"], "-5.2 14.6 11.2": ["consensuses"], "17.0 9.5 15.1": ["diddle"], "-1.9 6.6 7.8": ["obvs"], "-2.7 7.4 8.1": ["gearchange"], "11.1 22.1 18.9": ["putrefaction"], "2.4 -1.5 -4.6": ["gazettes"], "4.5 10.2 2.8": ["liek"], "10.4 4.5 12.8": ["keggers"], "3.1 1.3 5.1": ["reflexologist"], "9.3 7.2 11.5": ["sippin"], "18.3 16.7 4.8": ["pockmark"], "15.1 21.3 12.6": ["splicers"], "6.9 4.6 12.1": ["agglomerate", "binner"], "-3.2 -0.6 17.3": ["shipbrokers"], "2.4 3.2 8.1": ["digipak"], "13.1 15.0 6.6": ["immortalizes"], "8.1 10.1 13.1": ["magnolialover"], "0.5 9.5 5.3": ["shoutouts"], "9.6 8.6 8.8": ["washbasins"], "-4.1 30.9 2.2": ["shahid"], "7.3 16.1 4.8": ["thermite"], "8.5 12.8 15.2": ["lowermost"], "12.6 10.5 10.9": ["passerbys"], "26.8 -2.7 2.6": ["supergiant"], "11.8 -1.3 13.4": ["philadelphia"], "-1.5 -4.1 12.4": ["breastfeeds"], "15.7 -0.1 10.4": ["cartload"], "-7.8 -0.2 11.6": ["spermatogenesis"], "19.4 1.9 6.3": ["gramophones"], "7.9 3.1 32.5": ["gelati"], "8.8 13.6 3.6": ["pressurisation"], "3.8 4.4 -1.1": ["serveral"], "1.9 21.6 6.6": ["plaintext"], "14.2 18.7 24.0": ["poppa"], "-3.2 14.1 -0.3": ["bcos"], "2.6 6.6 6.4": ["superfamily"], "4.1 7.5 4.6": ["tautness"], "12.2 -2.1 -1.4": ["sevices"], "2.7 0.5 16.6": ["tutti"], "0.9 1.4 8.8": ["flouride"], "5.5 0.2 3.6": ["gigajoules"], "1.8 14.6 6.2": ["legalisms"], "-3.4 12.4 5.5": ["discrepant"], "9.9 15.4 11.8": ["cauterized"], "-2.8 4.2 16.5": ["fuelwood"], "8.8 14.0 17.1": ["superabundance"], "13.1 14.3 9.0": ["technocracy"], "7.7 9.2 8.2": ["glimmerings"], "20.3 6.2 6.5": ["toolshed"], "-7.9 5.6 11.5": ["cullet"], "3.4 14.7 15.7": ["outswingers"], "5.4 11.8 12.0": ["ativan"], "10.5 10.0 9.7": ["memphis"], "-5.0 -2.7 2.8": ["ketone"], "8.4 23.4 15.0": ["sneakiness"], "1.0 9.3 1.9": ["althought"], "20.8 1.5 16.5": ["porta"], "12.6 7.5 32.4": ["satsuma"], "3.7 13.8 16.7": ["veepstakes"], "13.2 19.3 6.1": ["beholders"], "7.4 30.2 0.2": ["targetable"], "-2.0 11.5 8.3": ["psychoanalytical"], "8.4 6.4 19.6": ["carhops"], "5.7 1.5 -1.1": ["repor"], "7.5 13.1 5.9": ["righter"], "-0.3 7.1 12.2": ["bushwalk", "julie"], "-2.0 18.4 -0.8": ["demobbed"], "-0.5 -4.6 1.1": ["apr"], "18.9 14.3 17.3": ["pinballs"], "-2.1 17.6 3.4": ["particularily"], "8.3 1.4 13.9": ["panelized"], "6.4 8.6 24.7": ["mainsheet"], "1.4 43.6 9.9": ["firebase"], "2.3 12.5 4.9": ["pyschological"], "-4.7 -7.7 2.2": ["ities"], "3.0 11.5 5.0": ["bilayer"], "1.3 12.7 2.2": ["pacemaking"], "2.4 11.9 15.7": ["ryots"], "9.4 13.2 14.4": ["traditonal"], "6.0 1.2 7.3": ["peut"], "7.1 7.6 3.6": ["venter"], "0.4 11.4 9.0": ["shane"], "0.5 16.1 14.9": ["fedor"], "14.6 13.4 27.0": ["ambrosial"], "-9.6 9.4 11.1": ["temperment"], "7.6 12.8 8.1": ["surpassingly"], "2.6 35.3 19.2": ["frags"], "-1.6 15.6 5.7": ["idolization"], "15.0 22.7 14.4": ["impalement"], "2.4 -5.0 8.9": ["folklorists"], "7.4 1.2 2.5": ["showcar"], "10.6 9.0 15.7": ["grinnin"], "11.2 11.5 3.8": ["innumerate"], "16.2 6.0 7.1": ["toyshop"], "6.7 10.5 9.4": ["captivatingly"], "7.6 11.0 9.7": ["tryna"], "1.9 13.0 8.1": ["urbanists"], "-8.1 8.9 9.1": ["requalification"], "8.9 13.9 13.6": ["villi"], "4.7 8.7 9.1": ["smashingly"], "8.2 13.0 10.4": ["aviatrix"], "1.0 5.9 14.4": ["windrow"], "1.5 3.5 14.9": ["hypertrophic"], "-0.6 6.4 8.0": ["oclock"], "6.8 8.0 0.9": ["adjustors"], "-0.9 8.0 -2.5": ["firewalled"], "3.2 2.0 20.5": ["runanga"], "4.8 6.6 1.1": ["succeded"], "-2.4 7.5 19.3": ["masalas"], "8.1 12.6 11.8": ["homeplate"], "-4.5 9.8 7.5": ["followups"], "16.4 3.8 22.8": ["blondie"], "-1.9 8.8 12.0": ["flystrike"], "2.7 3.2 3.0": ["scriptable"], "-2.9 2.4 5.0": ["lavage"], "8.2 3.7 5.4": ["flushable"], "6.2 -0.6 10.4": ["microbusinesses"], "9.2 13.3 1.2": ["dificult"], "17.0 13.2 17.9": ["trackhoe"], "5.6 -0.6 8.0": ["aresult"], "-12.0 10.0 2.4": ["psychotherapies"], "-5.1 6.0 3.7": ["laparotomy"], "1.1 4.4 10.2": ["medicalization"], "1.8 -0.5 -4.9": ["offerred"], "3.9 7.9 28.7": ["caesar"], "17.9 2.2 29.9": ["mache"], "2.9 4.7 36.3": ["alfredo"], "7.6 0.1 19.6": ["tas"], "23.2 13.0 11.8": ["pock"], "13.8 7.7 12.9": ["faade"], "8.2 14.1 13.7": ["imperiousness"], "8.2 6.8 28.0": ["dockmaster"], "10.8 6.1 17.6": ["unshaved"], "8.7 3.4 28.4": ["pierogis"], "7.6 10.0 5.4": ["videocameras"], "5.8 6.3 19.9": ["towline"], "-6.4 5.4 10.4": ["conditons"], "23.5 11.3 6.7": ["haloed"], "3.9 12.8 9.2": ["sitemaps"], "5.1 22.0 18.4": ["buffelgrass"], "7.7 2.3 13.1": ["pjs"], "8.0 17.0 6.8": ["dunderhead"], "2.9 17.1 11.5": ["raison"], "1.8 2.8 -0.1": ["inserters"], "8.0 17.2 12.4": ["latitudinal"], "7.1 -12.3 10.6": ["cohosted"], "4.8 19.1 3.3": ["bast"], "6.7 15.4 30.2": ["hackle"], "7.9 7.7 11.7": ["brunet"], "1.7 8.8 -0.6": ["whish"], "6.9 -5.0 13.3": ["beyonce"], "-0.0 12.5 11.3": ["annualizing"], "6.5 6.1 9.3": ["jro"], "1.2 15.2 7.1": ["habituate"], "12.4 5.6 13.2": ["downhome"], "5.8 14.1 -4.5": ["controll"], "-1.2 3.5 17.2": ["sindoor"], "8.2 -0.8 7.3": ["meer"], "7.4 3.0 3.4": ["stuggling"], "-1.1 11.5 3.1": ["azan"], "-1.4 11.4 -1.9": ["xxv"], "-3.1 0.9 8.8": ["sherwanis"], "9.8 11.1 5.4": ["biometrically"], "2.5 8.0 -3.3": ["acclaiming"], "-2.3 3.5 2.5": ["adoptability"], "-1.0 14.4 8.0": ["kitman"], "-0.2 6.6 23.7": ["matza"], "5.1 10.8 10.5": ["splenetic"], "7.4 9.6 31.5": ["waggler"], "-10.5 28.0 2.4": ["shaheed"], "8.1 13.7 3.3": ["princeling"], "20.5 17.6 12.0": ["refracting"], "-0.9 2.3 11.8": ["romidepsin"], "19.8 10.5 17.2": ["birdcages"], "1.0 0.8 1.4": ["transpromo"], "1.8 8.1 6.8": ["ios"], "5.1 -6.6 5.4": ["tran"], "9.3 11.4 14.8": ["pingers"], "-8.8 2.9 7.9": ["gaveling"], "1.4 12.8 5.1": ["tryscorers"], "5.2 15.1 8.2": ["sightseer"], "4.7 -3.3 6.2": ["jewlery"], "18.0 5.5 30.4": ["hoochie"], "10.4 7.6 9.9": ["backliner"], "9.7 12.8 12.4": ["lesbo"], "8.0 20.3 9.9": ["scarey"], "-11.5 2.8 1.5": ["claimable"], "8.7 7.6 11.7": ["tivo"], "12.7 0.6 0.1": ["aleady"], "1.0 19.5 13.4": ["religio"], "-2.6 17.8 12.0": ["postmodernists"], "-5.3 11.9 10.2": ["celiacs"], "1.8 -1.9 8.3": ["freezed"], "12.2 3.6 3.7": ["iq"], "8.4 6.9 14.1": ["geotextile"], "15.5 9.9 14.8": ["gameshows"], "4.6 5.2 4.0": ["exergaming"], "-11.2 0.3 6.0": ["hematomas"], "9.4 3.9 14.3": ["glaziers"], "29.3 31.3 17.7": ["armadas"], "6.9 6.0 16.1": ["hairlines"], "8.9 11.8 10.1": ["reproachful"], "3.3 8.9 15.3": ["coxless"], "1.5 15.4 12.0": ["repub"], "11.2 9.2 3.2": ["architectonic"], "0.9 4.9 5.2": ["geoexchange"], "3.9 19.3 8.6": ["essentialist"], "5.0 6.1 28.1": ["chewiness"], "13.3 6.0 27.7": ["millpond"], "2.0 7.1 8.4": ["picturisation"], "-8.0 1.5 12.5": ["freeskate"], "8.4 1.5 34.7": ["yuca"], "19.1 13.5 9.5": ["wonderous"], "2.4 3.5 7.9": ["rly"], "4.9 32.2 4.2": ["intimidators"], "7.8 4.9 14.1": ["sconce"], "6.3 20.1 13.6": ["sledder"], "8.9 9.3 10.6": ["stultified"], "5.8 8.9 11.2": ["bloggy"], "3.4 13.0 2.4": ["prided"], "-1.0 29.2 7.8": ["palestinians"], "17.0 17.1 5.6": ["acquiree"], "5.5 4.2 13.5": ["duodenal"], "-8.5 -0.9 3.9": ["remittitur"], "6.8 12.9 10.9": ["adjectival"], "-2.8 20.8 -5.1": ["assasinated"], "-0.5 4.0 14.9": ["sae"], "5.8 9.3 13.0": ["railbed"], "-1.8 8.6 7.0": ["wellbores"], "24.8 10.8 8.2": ["dartboards"], "6.9 6.5 11.3": ["porticos"], "4.0 -1.3 5.0": ["ohn"], "4.6 21.7 10.6": ["commonness"], "1.9 13.6 8.6": ["motorization"], "-2.8 11.5 7.5": ["assents"], "-1.3 13.0 3.9": ["egregiousness"], "0.2 -1.0 5.6": ["haws"], "8.2 14.9 12.5": ["blaugrana"], "1.6 15.0 2.9": ["sikhs"], "4.3 6.8 5.1": ["foley"], "3.9 -0.4 4.3": ["multisource"], "-8.5 6.5 7.1": ["resettlements"], "13.8 1.8 22.1": ["corned"], "2.7 14.0 17.3": ["isothiocyanates"], "6.4 14.9 9.2": ["impressiveness"], "21.7 8.4 26.4": ["kookaburra"], "12.9 -3.7 6.7": ["begain"], "13.6 4.3 5.5": ["ampm"], "2.5 15.4 6.6": ["exclave", "unpressurized"], "7.6 13.1 30.1": ["foraminifera"], "16.5 10.1 11.1": ["prefigures"], "5.3 9.4 20.1": ["sepals"], "8.1 9.4 19.2": ["softwoods"], "5.0 12.8 5.8": ["freeness"], "4.8 8.0 9.8": ["disfunction"], "-3.1 17.4 0.5": ["homeguards"], "5.9 -6.3 13.1": ["ele"], "14.2 25.6 9.4": ["fearmongers"], "11.6 7.2 4.6": ["incidently"], "5.0 11.6 6.4": ["immigrates"], "4.1 0.1 5.4": ["preauthorization"], "6.1 0.6 11.8": ["sclera"], "5.3 17.7 4.3": ["jeremiads"], "21.4 14.2 12.3": ["splicer"], "3.2 11.0 9.8": ["clickthrough"], "-2.6 3.7 12.5": ["pont"], "7.5 3.3 7.7": ["adm"], "-0.4 -3.1 6.1": ["hirsutism"], "-1.1 12.0 9.1": ["downlinks"], "3.1 27.8 4.3": ["shellshock"], "-0.5 -3.4 0.8": ["keynoters"], "1.5 -0.6 8.7": ["outwear"], "6.0 5.1 21.6": ["doner"], "16.3 19.1 15.9": ["noonday"], "19.6 12.8 3.9": ["enfolding"], "3.5 23.6 7.4": ["emancipator"], "-4.1 -10.7 -0.1": ["firsttime"], "6.4 15.5 10.3": ["teleological"], "1.1 2.2 10.4": ["philatelists"], "9.6 13.6 27.0": ["lapwings"], "19.2 16.0 20.3": ["whomping"], "-5.8 -1.8 7.7": ["singings"], "2.8 11.6 4.2": ["excitations"], "5.4 15.8 6.4": ["certitudes"], "12.6 24.0 3.6": ["braveheart"], "0.6 9.1 21.2": ["nonreactive"], "15.1 15.0 13.1": ["interruptus"], "7.4 8.3 12.8": ["matthew"], "-2.8 5.0 0.4": ["expectancies"], "-0.8 15.0 4.0": ["curtilage"], "7.1 11.0 5.0": ["unshaded"], "6.2 10.1 7.7": ["quantization"], "8.1 -2.6 11.2": ["cooperage"], "3.0 13.9 18.8": ["trichinosis"], "5.2 12.7 3.7": ["thw"], "3.6 9.7 10.5": ["ostinato"], "17.0 14.8 8.4": ["goggled"], "0.4 20.7 9.8": ["equidistance"], "8.2 -8.5 5.0": ["nella"], "5.4 3.5 13.9": ["tara"], "5.0 2.8 3.3": ["hadbeen"], "-8.7 4.7 8.0": ["pseudowire"], "10.4 3.6 17.9": ["rollups"], "21.2 18.0 18.2": ["chuckers"], "6.3 1.6 9.5": ["reabsorption"], "13.9 16.0 7.7": ["frighteners"], "-2.1 26.9 10.2": ["uncompassionate"], "-2.7 7.4 3.1": ["disinvite"], "-7.8 4.5 12.0": ["gunlocks"], "6.0 -2.6 -8.2": ["adresses"], "0.3 7.1 11.0": ["liz"], "26.9 14.7 24.2": ["gloop"], "5.1 9.6 -0.1": ["twitted"], "7.0 -7.0 6.2": ["inv"], "7.9 7.4 0.4": ["employess"], "-5.6 6.9 0.8": ["eglue"], "2.0 2.6 -2.1": ["projectiondesign"], "1.2 19.7 9.2": ["sketchily"], "8.3 -1.6 6.5": ["lapdance"], "0.9 6.3 4.2": ["imagistic"], "-6.8 8.8 5.2": ["passangers"], "4.1 1.3 6.7": ["obo"], "-4.1 8.7 0.3": ["xxiv"], "8.4 20.5 24.2": ["naga"], "6.5 8.3 1.2": ["reevaluates"], "8.3 12.0 12.5": ["jobsworth"], "1.7 -2.4 9.8": ["microfiltration"], "0.9 0.2 -8.8": ["wrt"], "2.1 3.2 18.1": ["broadloom"], "4.7 -0.4 3.4": ["streetlighting"], "7.7 1.5 8.3": ["citings"], "6.3 10.7 14.9": ["kak"], "11.6 3.6 21.0": ["tetrapod"], "16.8 3.1 14.9": ["squeezebox"], "11.5 -1.1 10.0": ["kr"], "23.1 11.1 30.6": ["inukshuk"], "5.0 -0.0 8.3": ["artista"], "1.1 -8.5 5.3": ["prattled"], "-7.3 4.7 27.8": ["winegrapes"], "13.6 26.4 11.5": ["demonically"], "10.0 13.8 -0.6": ["loosers"], "1.7 16.1 2.8": ["esprit"], "2.8 11.8 1.8": ["sagittal"], "8.2 7.1 28.1": ["grebe"], "7.1 -3.8 4.6": ["ormer"], "6.5 7.4 20.7": ["mummers"], "-1.7 1.6 3.0": ["indi"], "15.5 21.6 10.1": ["nonliving"], "4.1 2.2 9.7": ["encashing"], "3.5 2.6 12.2": ["regu"], "-8.4 -0.8 15.1": ["arabicas"], "4.7 7.1 7.9": ["gabardine"], "1.2 9.0 9.3": ["gratifications"], "1.7 6.5 10.2": ["regifted"], "23.1 18.4 10.7": ["squishes"], "0.6 9.4 14.1": ["surficial"], "-5.1 20.4 6.2": ["abolitionism"], "11.9 9.8 4.6": ["undreamt"], "13.3 5.2 21.9": ["wampum"], "18.3 10.1 19.1": ["biomorphic"], "-8.6 11.4 4.1": ["avgas"], "6.8 0.6 4.0": ["whitener"], "-5.1 -0.5 18.5": ["sooji"], "14.6 7.8 18.1": ["glug"], "14.3 10.2 26.6": ["tinnie"], "3.4 7.4 11.4": ["snowmakers"], "18.3 5.9 16.1": ["breadmaker"], "10.5 11.2 -1.9": ["unmistakeably"], "9.3 7.3 4.3": ["valise"], "8.8 17.2 37.0": ["buzzbait"], "-2.7 12.0 -0.5": ["diagnostically"], "10.9 17.0 14.4": ["screwballs"], "5.8 17.0 23.7": ["tenderizing"], "6.1 16.7 8.6": ["patronisingly"], "11.1 9.0 19.0": ["cookhouse"], "2.1 8.0 14.2": ["punctuations"], "4.4 5.3 7.0": ["bywords"], "6.6 6.0 -0.3": ["trivialisation"], "-4.7 7.3 2.6": ["outfinished"], "19.0 18.5 15.7": ["newsies"], "18.3 23.1 25.8": ["mudhole"], "13.1 7.7 3.9": ["rectums"], "6.1 3.1 13.8": ["hipbone"], "2.7 12.9 9.6": ["ribozyme"], "4.8 15.1 4.3": ["fetishization"], "12.4 8.3 7.0": ["unsightliness"], "9.6 28.2 -5.0": ["brownshirts"], "1.5 4.4 12.8": ["teri"], "14.4 0.9 11.7": ["tackier"], "0.6 6.4 11.5": ["kal"], "4.5 -2.4 7.7": ["tohave"], "-3.9 4.5 2.1": ["hist"], "1.3 13.2 4.3": ["tring"], "18.6 17.1 13.1": ["prestidigitation"], "3.8 6.2 8.5": ["interbedded"], "7.5 11.9 11.3": ["shippable"], "-7.4 7.8 12.2": ["irrigations"], "8.7 8.4 3.7": ["multivalent"], "-0.1 8.4 6.6": ["europium"], "-5.2 18.9 9.2": ["clergyperson"], "-9.2 7.0 4.4": ["nommed"], "10.4 3.0 16.9": ["cabinetmaking"], "17.2 6.6 14.5": ["cufflink"], "5.1 15.8 10.4": ["preciseness"], "-0.0 4.5 15.4": ["southbridge"], "9.2 11.1 0.5": ["euroskeptic"], "14.0 6.6 6.7": ["homevid"], "12.6 13.8 -0.1": ["ionised"], "11.8 4.3 1.3": ["striken"], "-3.7 12.6 6.1": ["inthis"], "4.9 4.0 3.9": ["possibily"], "5.6 24.2 -1.1": ["brainwashes"], "0.3 3.2 7.2": ["spectrophotometers"], "11.2 15.8 -6.5": ["highjack"], "11.2 4.0 3.1": ["oon"], "-2.0 7.4 4.1": ["phono"], "10.4 1.9 18.2": ["bathtime"], "-3.9 9.5 10.7": ["mich"], "-8.4 2.2 11.0": ["librettists"], "8.8 -1.8 10.7": ["chainwide"], "9.3 3.1 5.2": ["tiene"], "10.4 14.8 8.5": ["dislocates"], "15.7 17.6 7.7": ["grandiosely"], "2.3 3.7 2.9": ["reconcilation"], "3.9 -4.2 14.4": ["tina"], "-3.5 5.5 3.8": ["hypnotics"], "3.3 2.1 1.9": ["doit"], "10.1 6.3 10.8": ["pantless"], "2.7 11.9 6.1": ["perturbs"], "-5.4 14.1 5.3": ["magnifications"], "8.3 12.7 1.1": ["hawkeye"], "3.7 3.1 -1.2": ["trhe"], "13.5 12.2 12.0": ["anticlockwise"], "-5.2 17.2 -3.5": ["deponent"], "5.6 15.7 3.6": ["leitmotifs"], "14.2 6.2 16.2": ["babushka"], "1.6 20.7 17.4": ["larvicides"], "-2.4 -2.5 8.5": ["lowincome"], "-5.6 0.9 -8.5": ["toprovide"], "7.2 3.8 0.2": ["ehealth"], "-2.2 3.1 8.9": ["metalsmith"], "5.1 11.9 3.2": ["excommunicating"], "5.9 33.9 7.3": ["counterstrikes"], "-0.4 7.8 10.3": ["youngins"], "6.4 10.8 11.2": ["exascale"], "5.0 8.4 7.1": ["beguiles"], "3.1 25.3 0.3": ["unsurvivable"], "15.8 5.2 3.1": ["blinging"], "-7.0 4.5 6.3": ["subcortical"], "11.9 10.4 10.7": ["geodata"], "-10.6 11.2 8.7": ["legitimates"], "15.4 10.9 16.3": ["whomped"], "4.5 9.2 8.0": ["litanies"], "2.8 2.0 7.9": ["accruable"], "6.8 5.3 9.0": ["newboys"], "8.3 19.9 2.3": ["depressurize"], "3.8 9.6 -4.8": ["confortable"], "14.8 10.7 10.9": ["whop"], "4.1 21.8 -2.0": ["revolutionist"], "5.5 9.7 22.9": ["manuka"], "3.0 6.6 3.0": ["multivolume"], "17.1 -2.3 11.0": ["pedway"], "-1.9 6.4 0.4": ["somoni"], "17.8 6.3 12.7": ["vitrines"], "-1.5 2.8 7.5": ["datapath"], "16.1 17.8 3.4": ["rumormongers"], "16.4 17.6 4.4": ["contol"], "6.0 5.6 7.5": ["sof"], "3.7 6.2 18.6": ["toter"], "2.3 -0.2 5.7": ["downlight"], "8.6 16.2 16.3": ["maneater"], "-10.9 9.8 2.3": ["recantations"], "7.6 0.1 4.7": ["postmarket"], "1.9 18.5 0.9": ["secularize"], "4.9 -1.8 13.2": ["octal"], "3.0 13.9 10.5": ["metrical"], "15.7 27.4 21.4": ["backstabbers"], "9.6 12.3 7.3": ["woth"], "8.6 6.3 1.1": ["frittering"], "-1.9 1.1 6.3": ["serialize"], "6.9 7.6 21.5": ["cerveza"], "1.9 4.7 3.0": ["gotalk"], "9.5 -0.8 2.2": ["floorcoverings"], "1.4 -0.1 11.8": ["fractionators"], "16.6 14.7 1.2": ["awing"], "8.7 7.2 8.9": ["gad"], "-2.4 1.9 9.0": ["reindicted"], "5.8 8.2 19.8": ["creekbed"], "7.3 17.2 17.4": ["timberline"], "-3.8 12.2 9.1": ["permissable"], "3.0 5.4 4.6": ["astrologist"], "4.7 8.2 4.9": ["numerologists"], "12.6 23.8 9.1": ["unseeable"], "-0.9 5.0 3.6": ["havea"], "16.6 14.2 20.9": ["riggings"], "-3.5 12.4 5.9": ["attosecond"], "4.2 5.7 14.6": ["deepness"], "6.9 14.3 9.8": ["sighter"], "14.3 6.3 2.8": ["jst"], "8.8 7.0 16.3": ["puggle"], "-5.8 18.8 -0.9": ["deprogram"], "23.2 16.9 7.2": ["weilding"], "3.5 9.2 1.4": ["enmasse"], "10.2 15.6 8.8": ["smarty"], "13.6 15.6 23.8": ["campmates"], "-1.6 6.7 0.6": ["permanant"], "2.8 7.2 3.8": ["helpdesks"], "-0.1 -1.0 9.6": ["multimanager"], "4.3 10.4 8.3": ["comix"], "0.0 9.0 7.6": ["depositional"], "13.1 6.8 7.1": ["cleated"], "11.6 5.5 10.6": ["apse"], "-1.3 6.6 16.2": ["raconteurs"], "9.8 14.3 37.0": ["hardheads"], "-6.1 4.7 1.8": ["busways"], "3.6 11.7 6.1": ["midcourter"], "5.4 9.2 11.7": ["megadoses"], "15.5 4.1 8.1": ["soc"], "9.3 -4.3 1.0": ["footcare"], "-6.6 15.4 3.6": ["countermanding"], "-13.3 8.3 2.5": ["deactivations"], "15.6 3.1 5.6": ["shh"], "-2.1 4.1 0.9": ["conveyancer"], "11.9 18.3 11.1": ["primitively"], "6.3 7.4 7.6": ["nwanews"], "24.8 15.1 9.3": ["fatcats"], "2.7 5.4 8.4": ["minivehicle"], "10.4 17.0 11.1": ["deadness"], "1.6 7.0 6.5": ["nonscholarship"], "2.9 -3.7 18.7": ["pickguard"], "17.4 9.2 16.3": ["gunky"], "6.6 2.1 5.5": ["shoudl"], "7.3 8.0 6.7": ["frontispiece"], "13.5 20.1 29.7": ["earwig"], "-2.2 9.7 13.7": ["stockpicking"], "13.5 13.5 4.8": ["bastardize"], "15.0 10.8 6.1": ["proceded"], "4.8 6.3 -1.9": ["individualisation"], "16.7 7.8 0.7": ["bazillions"], "2.1 5.5 2.5": ["maxillofacial"], "11.5 1.9 5.6": ["opn"], "1.6 15.2 2.9": ["ashame"], "7.7 11.1 26.6": ["cloches"], "20.8 4.1 12.4": ["rollerskates"], "1.8 6.4 5.1": ["defreezing"], "20.9 10.9 12.4": ["googles"], "0.7 -1.8 20.7": ["foodbanks"], "13.6 15.6 14.7": ["cannibalizes"], "-1.2 -0.4 7.6": ["overprinting"], "6.6 26.3 5.3": ["armyman"], "11.7 -1.0 -0.3": ["anouncement"], "6.0 11.1 23.4": ["trimarans"], "0.8 0.9 5.9": ["pterostilbene"], "0.0 18.8 13.5": ["footspeed"], "2.3 -0.9 0.9": ["conservatorships"], "3.1 13.8 8.5": ["poleward"], "-0.9 9.6 7.6": ["cuprates"], "13.6 8.7 3.1": ["captivation"], "-10.6 -0.9 1.1": ["caesarian"], "7.4 9.0 15.0": ["campbell"], "0.8 -0.8 6.3": ["heydey"], "-6.5 4.3 10.3": ["annuitization"], "7.0 19.1 3.5": ["quantized"], "0.6 9.8 10.7": ["datastore"], "10.4 5.2 28.3": ["momos"], "-4.0 -2.8 17.1": ["hanggang"], "0.8 11.6 17.0": ["rainshowers"], "7.4 2.6 9.2": ["cml"], "5.5 6.9 9.2": ["subroutines"], "-0.4 -5.9 4.9": ["delievered"], "12.1 13.3 14.3": ["conniption"], "8.9 31.7 10.6": ["destabilizers"], "7.9 18.4 20.2": ["symbionts"], "-10.9 2.4 12.1": ["humbucker"], "3.2 7.0 5.2": ["azaan"], "15.4 4.6 25.6": ["splendiferous"], "1.8 29.7 3.1": ["seditionists"], "-0.1 10.1 6.7": ["milliwatt"], "4.2 9.9 14.2": ["underweighting"], "-5.8 19.0 4.3": ["loadmasters"], "30.6 16.0 11.3": ["gamemaker"], "1.3 10.5 19.2": ["kama"], "0.9 12.1 7.1": ["decarbonisation"], "0.1 13.3 10.8": ["demystification"], "2.0 2.0 0.3": ["telecentres"], "6.7 14.3 10.4": ["saturnine"], "-3.4 9.8 -0.6": ["reestablishes"], "0.6 12.0 13.4": ["jt"], "14.9 5.9 7.2": ["catchline"], "13.6 6.7 11.3": ["roboticists"], "7.3 2.4 9.4": ["featherbedding"], "8.7 2.7 13.7": ["franklin"], "14.6 12.6 18.3": ["hambone"], "7.0 13.2 6.0": ["turkish"], "0.5 14.5 0.9": ["ionisation"], "1.1 0.1 7.9": ["homoeopathic"], "8.9 9.4 11.7": ["cueman"], "9.2 11.9 31.3": ["planktonic"], "9.1 7.8 18.6": ["bathymetry"], "-0.0 19.7 6.5": ["biothreat"], "-4.9 11.9 13.0": ["completer"], "6.0 1.1 10.7": ["steamiest"], "27.4 16.0 26.6": ["muncher"], "3.1 5.5 14.8": ["greenspaces"], "5.5 1.9 -2.8": ["kidthing"], "6.9 6.7 52.8": ["cabezon"], "5.7 1.9 38.7": ["oxtails"], "1.3 0.4 13.8": ["iba"], "9.9 5.1 35.8": ["smokies"], "6.6 2.2 11.1": ["mortages"], "7.8 7.5 17.4": ["gordon"], "2.5 -3.0 0.6": ["arrangment"], "2.7 4.8 14.8": ["auditionees"], "6.8 2.3 14.3": ["sleepout"], "3.7 7.9 14.0": ["evans"], "13.7 11.8 8.6": ["slewed"], "-4.7 24.5 2.7": ["malik"], "5.0 6.7 13.7": ["cron"], "13.7 5.5 -4.9": ["centralises"], "1.5 11.1 5.6": ["indeterminacy"], "10.3 7.2 21.7": ["balti"], "5.1 12.9 18.3": ["cussin"], "9.4 4.3 8.3": ["oxer"], "1.3 0.4 15.6": ["replantation"], "2.2 11.1 3.1": ["systemized"], "3.3 8.9 17.8": ["posada"], "-13.4 -1.5 -1.2": ["dialysate"], "6.3 6.7 2.0": ["discountenance"], "-7.9 11.5 2.8": ["endnote"], "1.6 2.9 3.7": ["prolix"], "5.1 5.4 11.0": ["wavelet"], "19.9 15.1 15.6": ["fathomless"], "4.4 11.4 6.1": ["whould"], "-2.9 2.0 3.3": ["notarial"], "1.2 5.3 35.2": ["pancit"], "9.8 7.2 5.1": ["slicking"], "5.9 7.7 8.0": ["bana"], "-9.5 8.7 2.3": ["pathophysiological"], "8.1 9.5 18.9": ["sizzlers"], "-1.4 6.3 14.7": ["torchy"], "-4.7 16.7 -1.6": ["whereabout"], "5.0 -7.9 34.4": ["flautas"], "1.3 3.9 7.8": ["espcially"], "20.2 8.5 16.0": ["quadrillions"], "-10.3 8.2 0.2": ["notings"], "9.7 3.0 -5.8": ["minsters"], "10.9 3.0 18.3": ["dubby"], "15.1 7.9 0.8": ["genuflected"], "5.1 20.9 2.5": ["bodys"], "3.8 3.2 6.6": ["cuando"], "10.1 8.5 14.2": ["metagenomics"], "-0.9 2.7 2.9": ["prioress"], "-12.6 4.2 5.5": ["dower"], "1.5 9.5 -2.6": ["reformations"], "-1.8 16.9 8.7": ["galamsey"], "3.0 12.5 5.0": ["deflowered", "lokayukta"], "10.7 -0.0 10.4": ["amanda"], "10.0 10.9 15.0": ["floozies"], "0.3 0.3 0.6": ["ophthalmological"], "8.1 14.5 14.1": ["rogueware"], "4.6 8.9 5.3": ["loupe"], "2.4 14.0 6.5": ["nystagmus"], "6.7 0.7 8.6": ["castrations"], "20.5 26.0 19.6": ["wraiths"], "14.8 4.0 17.2": ["fluting"], "5.5 13.8 11.8": ["matriarchy"], "-1.3 14.5 11.3": ["upback"], "5.1 23.5 12.0": ["uttermost"], "-8.1 6.2 0.9": ["antiepileptic"], "11.6 -1.2 4.0": ["souping"], "-2.8 -0.6 5.8": ["meniscal"], "0.8 12.7 8.2": ["concealable"], "1.4 13.4 5.5": ["romanticising"], "9.5 4.7 5.6": ["nitrocellulose"], "8.2 3.4 34.8": ["bolognese"], "-1.0 19.6 0.7": ["localizer"], "3.5 12.9 -0.3": ["clergies"], "10.8 11.2 42.2": ["mackinaw"], "-2.9 2.2 10.1": ["suspensory"], "3.7 4.7 -1.9": ["recommission"], "7.7 16.2 13.6": ["unenthusiastically"], "4.7 7.9 14.0": ["foreach"], "0.7 10.5 9.2": ["greensomes"], "-7.5 10.8 -4.5": ["psychodynamic"], "16.4 12.7 11.9": ["huzzah"], "-1.2 7.3 16.9": ["overpumping"], "11.8 5.8 6.3": ["trioval"], "12.8 5.9 2.9": ["perenially"], "2.7 13.7 7.9": ["dispersive"], "13.0 25.2 11.3": ["entropic"], "4.9 18.9 10.5": ["nosiness"], "0.9 9.3 12.0": ["overprint"], "-2.0 6.6 7.5": ["flyback"], "4.4 11.5 1.1": ["rebuilder"], "2.2 -4.5 1.1": ["layettes"], "-3.3 5.5 4.4": ["subseries"], "4.3 6.4 7.7": ["tourers"], "4.4 2.8 15.4": ["saka"], "2.8 12.3 5.6": ["everton"], "9.9 4.0 37.3": ["fusilli"], "7.8 9.6 4.7": ["terawatts"], "20.7 3.3 19.2": ["fulls"], "14.6 25.3 13.7": ["braggarts"], "9.2 5.2 6.7": ["abiraterone"], "9.8 28.4 9.4": ["pwn"], "12.5 14.7 5.9": ["europeans"], "2.8 15.9 14.0": ["yadra"], "-0.8 -7.1 11.8": ["preconcert"], "14.9 21.8 16.2": ["submissively"], "3.7 5.3 12.7": ["abraded"], "-0.6 11.6 3.8": ["nonfuel"], "9.9 18.8 -1.9": ["kinetically"], "-1.5 14.7 -0.6": ["suborned"], "1.5 4.6 12.8": ["nanogenerator"], "3.9 22.2 3.0": ["revenged"], "2.8 11.5 11.5": ["ethnologist"], "10.1 13.1 34.4": ["ungulate"], "-5.9 8.5 -2.3": ["modularization"], "-7.8 -0.6 5.9": ["articling"], "4.6 9.6 5.5": ["depressives"], "-5.5 9.1 -0.6": ["operatively"], "12.5 13.3 19.2": ["homonyms"], "12.8 13.2 16.3": ["stubbled"], "14.1 21.7 24.1": ["slaver"], "-0.5 8.0 13.2": ["clienteles"], "1.5 10.0 20.4": ["partyer"], "1.7 19.5 17.5": ["dropback"], "-4.5 5.4 4.8": ["intercalated"], "7.0 15.3 7.2": ["placates"], "-14.4 8.6 4.6": ["oophorectomy"], "13.2 11.8 10.9": ["buckaroos"], "19.5 19.3 -1.0": ["capabilites"], "-9.1 4.6 2.9": ["endodontic"], "1.1 26.1 -0.1": ["demilitarizing"], "6.5 9.1 17.8": ["lactobacillus"], "-2.5 1.8 6.0": ["mamlatdar"], "1.9 7.1 -2.3": ["shold"], "2.8 5.5 3.1": ["elating"], "0.3 -11.8 2.0": ["folowing"], "1.7 8.7 24.2": ["arrowroot"], "11.1 12.7 10.7": ["porkies"], "10.3 13.6 8.7": ["cuba"], "-1.9 15.5 11.3": ["gotra"], "8.3 3.5 8.3": ["dirndl"], "1.9 28.0 3.7": ["communalist"], "17.2 16.2 10.6": ["smackdowns"], "3.9 7.8 11.6": ["foglights"], "1.1 2.2 16.1": ["hydrolyzed"], "4.6 3.1 22.0": ["bents"], "1.2 16.3 1.1": ["polarizations"], "12.3 12.3 11.4": ["espied"], "0.1 17.5 4.1": ["logician"], "-1.7 0.7 10.9": ["refacing"], "4.4 10.8 12.7": ["foulout"], "1.4 -5.8 33.2": ["primavera"], "5.8 10.3 2.5": ["crorepati"], "10.3 28.6 12.8": ["insensate"], "0.8 3.5 5.6": ["pedagogues"], "0.9 24.5 7.3": ["assult"], "13.6 18.5 9.4": ["chatterboxes"], "4.8 15.9 27.1": ["saola"], "-5.4 7.8 7.3": ["salwar"], "8.0 2.8 15.6": ["afrobeat"], "0.8 24.2 2.9": ["inciter"], "11.5 17.7 13.9": ["snowploughs"], "5.2 8.3 6.0": ["conjecturing"], "0.1 3.5 12.9": ["regrind"], "-1.4 -2.7 15.8": ["hardener"], "-0.2 18.7 17.5": ["pyrethroid"], "17.5 16.6 17.2": ["smurfs"], "-1.4 5.4 6.0": ["seond"], "0.4 -1.1 2.7": ["expereince"], "12.7 28.8 24.6": ["skeeters"], "11.2 10.7 1.4": ["bruited"], "17.6 6.4 12.0": ["moneybag"], "11.6 17.8 11.0": ["pancaking"], "2.9 5.1 0.8": ["colorable"], "11.0 1.2 19.4": ["pigged"], "-1.0 11.3 12.0": ["elevens"], "1.8 14.7 29.1": ["tetrodotoxin"], "6.0 3.4 15.1": ["pashminas"], "3.2 4.1 16.0": ["triptychs"], "-4.8 15.1 11.0": ["noncontiguous"], "2.5 0.4 15.7": ["eyeshadows"], "1.3 1.1 11.5": ["cru"], "9.4 7.9 9.4": ["mantlepiece"], "-2.0 10.2 3.6": ["serogroups"], "5.0 16.4 -4.2": ["strategised"], "17.7 15.6 11.0": ["ecosphere"], "8.9 8.8 10.0": ["diwali"], "9.7 8.9 15.5": ["shiz"], "3.5 9.2 13.1": ["pernickety"], "9.0 9.5 7.1": ["unimaginatively"], "8.0 13.4 16.9": ["baksheesh"], "-8.5 24.2 4.3": ["demarches"], "3.7 4.1 12.6": ["relined"], "9.0 9.6 12.6": ["overbalanced"], "20.0 10.7 8.6": ["htc"], "5.2 5.8 7.4": ["unicode"], "16.6 25.4 16.5": ["hunker"], "6.3 14.3 6.4": ["taketh"], "23.5 16.9 10.9": ["conglomerations"], "7.0 7.5 14.3": ["pantsless"], "9.6 15.0 10.4": ["sunshield"], "9.8 4.8 -1.0": ["agreeement"], "-1.0 9.8 10.6": ["chalo"], "5.8 20.7 2.3": ["actualities"], "-10.0 7.6 3.3": ["allocution"], "5.8 8.9 7.1": ["chyron"], "6.9 -2.0 4.5": ["shar"], "3.8 12.2 8.7": ["sentimentalists"], "-0.2 9.3 9.3": ["hijra"], "6.7 10.0 26.3": ["oriole"], "-2.3 6.3 3.5": ["complexed"], "6.4 0.4 7.2": ["smoothened"], "3.7 1.7 10.8": ["dyers"], "-5.0 2.0 10.6": ["eniluracil"], "1.6 8.4 1.6": ["cashable"], "-2.1 17.1 6.0": ["kippah"], "-10.6 18.3 -5.4": ["acquaintanceship"], "5.9 12.6 18.2": ["scrambly"], "0.2 2.6 6.0": ["enteral"], "0.6 10.5 17.0": ["bushier"], "9.8 15.4 7.3": ["peopl"], "-7.2 4.1 2.1": ["pathobiology"], "4.7 26.3 10.4": ["unalterably"], "18.0 12.6 24.6": ["weiner"], "5.8 7.4 34.2": ["muscadine"], "4.1 0.0 16.8": ["nating"], "1.6 19.3 15.7": ["dyin"], "7.5 13.8 5.1": ["wantonness"], "2.8 16.5 5.7": ["cursorily"], "17.4 5.7 4.8": ["niet"], "-0.4 15.9 3.4": ["camcording"], "2.3 4.2 14.1": ["jc"], "-8.4 5.0 21.2": ["barbera"], "6.9 17.4 13.0": ["sower"], "-0.1 15.5 8.2": ["brusqueness"], "5.3 9.2 2.2": ["nitpicked"], "-1.9 17.0 1.6": ["deists"], "1.9 10.6 16.3": ["kua"], "6.0 2.9 2.3": ["railroader"], "1.0 6.6 -10.0": ["audiocassettes"], "-0.5 5.1 8.3": ["gappers"], "5.9 5.9 1.7": ["rebirths"], "13.6 12.6 3.7": ["miring"], "6.9 15.9 -3.7": ["condeming"], "-0.1 4.2 2.5": ["awarness"], "-6.7 5.0 1.7": ["ciclesonide"], "20.6 26.0 20.3": ["whomp"], "4.0 20.1 7.5": ["abilty"], "-1.3 5.3 -3.3": ["electrocardiography"], "5.6 5.3 3.8": ["epay"], "2.4 14.0 6.7": ["suavity"], "13.3 4.3 0.4": ["airconditioner"], "6.9 7.4 14.9": ["scalers"], "23.0 14.7 33.0": ["fishhooks"], "-0.9 -4.3 6.9": ["webcaster"], "15.7 9.7 1.7": ["satirises"], "3.9 -8.0 8.3": ["multiport"], "4.7 23.3 4.7": ["evac"], "9.0 -0.9 14.0": ["morphogenesis"], "-6.8 7.0 5.5": ["transgenderism"], "9.9 5.7 5.6": ["mozilla"], "13.2 6.6 14.0": ["arvo"], "7.4 0.9 20.7": ["plumpness"], "6.9 19.3 -1.3": ["proselytizer"], "12.5 22.2 8.3": ["tempter"], "9.1 18.6 9.0": ["technics"], "-1.0 13.8 9.1": ["centrosome"], "15.1 9.6 6.5": ["niftiest"], "21.0 7.3 22.6": ["lardy"], "8.0 8.1 15.5": ["calcio"], "9.4 10.8 35.2": ["sabayon"], "12.7 4.4 -3.4": ["jumbotrons"], "0.8 -0.7 3.9": ["yers"], "0.7 11.6 6.9": ["outdrawn"], "15.2 9.3 13.2": ["bolshy"], "9.6 3.3 20.7": ["nondairy"], "-9.4 -0.8 9.6": ["noncustodial"], "-2.2 10.4 4.4": ["inlaw"], "7.8 10.5 13.8": ["pluton"], "1.3 8.1 2.6": ["becase"], "17.4 0.3 9.7": ["tril"], "6.4 17.5 8.5": ["unfeminine"], "16.8 6.6 12.8": ["percolator"], "12.4 10.9 21.5": ["sogginess"], "10.0 13.7 13.6": ["reddit"], "-2.0 11.8 8.2": ["extensional"], "2.8 5.0 0.7": ["restrictors"], "-2.0 6.4 12.1": ["cumulation"], "1.3 14.1 1.7": ["awol"], "7.4 0.5 17.4": ["gra"], "8.9 15.0 7.2": ["disfigurements"], "3.1 14.0 9.8": ["cineaste"], "2.8 6.3 18.2": ["roan"], "12.1 9.9 12.3": ["mainstreet"], "3.8 16.3 5.9": ["freemasons"], "9.0 14.4 24.1": ["ferryman"], "4.2 15.9 4.2": ["doesnot"], "10.1 10.6 4.8": ["accosts"], "-4.6 17.1 -0.0": ["circumstantially"], "3.2 3.2 18.2": ["ilang"], "-0.1 7.2 13.1": ["fluoropolymers"], "7.2 19.6 7.7": ["antonym"], "15.7 22.8 5.1": ["webslinger"], "3.1 0.9 2.3": ["ase"], "19.5 17.3 21.0": ["marmite"], "8.1 5.7 12.0": ["talcum"], "2.8 15.5 13.2": ["chilliness"], "4.5 38.6 4.5": ["antitank"], "10.1 6.2 16.4": ["ponderosa"], "11.4 15.2 12.4": ["defecates"], "12.7 9.6 22.3": ["hulu"], "2.1 9.5 7.6": ["anandamide"], "8.1 -2.6 -6.4": ["sublicenses"], "4.5 -3.2 8.0": ["importante"], "11.4 11.7 17.2": ["mirthless"], "17.8 0.4 12.2": ["showbags"], "18.9 13.6 30.4": ["honkers"], "-1.0 0.4 0.9": ["masterplanning"], "6.1 0.6 10.9": ["cravats"], "-1.3 3.7 4.0": ["gurukul"], "6.5 12.3 8.5": ["happing"], "0.6 -9.2 4.7": ["nonguaranteed"], "-0.8 7.9 4.6": ["preambles"], "4.5 4.1 2.5": ["trifurcation"], "-0.9 1.1 7.2": ["todos"], "1.6 8.3 11.0": ["peccadillo"], "-13.2 18.6 -3.9": ["automaticity"], "15.2 1.8 15.1": ["trackway"], "15.2 19.7 9.9": ["hitler"], "-4.1 5.2 7.5": ["auditioner"], "3.1 7.9 1.1": ["achievability"], "3.2 10.2 3.5": ["universalize"], "4.9 5.4 17.0": ["sheesha"], "4.5 15.2 24.7": ["bilberry"], "15.4 9.4 28.4": ["vege"], "13.2 9.2 30.2": ["sakura"], "12.0 8.3 14.0": ["pluggers"], "10.9 0.3 15.7": ["colo"], "12.3 24.6 7.2": ["mythically"], "5.6 7.4 13.8": ["bueno"], "15.4 4.5 39.4": ["ponzu"], "7.7 -0.5 14.1": ["pharyngeal"], "19.2 13.6 23.1": ["putrefying"], "-0.6 6.6 -1.1": ["defalcation"], "-5.2 4.1 4.9": ["microliters"], "5.7 6.9 13.5": ["reinsures"], "19.3 18.9 11.3": ["pulverizes"], "5.1 5.2 16.9": ["bodyboarders"], "11.1 17.6 3.0": ["genious"], "5.5 -1.5 10.2": ["blouson"], "-0.9 14.1 13.7": ["uncontradicted"], "-0.9 5.2 1.6": ["availible"], "1.3 8.0 9.5": ["childern"], "15.8 9.3 13.8": ["commodify"], "-2.4 13.3 5.3": ["venire"], "7.5 4.3 5.2": ["possibile"], "2.3 10.2 6.0": ["unmounted"], "13.6 3.9 17.0": ["payloader"], "1.6 15.5 7.9": ["lumads"], "15.2 18.9 36.2": ["gunwale"], "4.7 6.7 8.4": ["cg"], "-1.2 0.9 4.3": ["backslid"], "3.5 15.7 5.9": ["agian"], "7.5 18.8 3.3": ["ionize"], "14.6 5.4 4.8": ["hippodrome"], "12.1 4.0 11.3": ["lairy"], "0.0 14.6 0.6": ["emissive"], "13.3 2.8 1.9": ["orignal"], "7.1 -1.6 8.1": ["ahn"], "1.6 2.1 11.7": ["stl"], "-8.7 0.7 3.5": ["cpt"], "-1.8 -3.0 7.1": ["rg"], "-7.1 9.7 5.1": ["ocassions"], "2.0 23.0 5.0": ["reviling"], "-1.7 13.9 7.7": ["syntactical"], "9.8 16.0 8.6": ["untranslatable"], "-2.8 20.1 -2.7": ["reeducate"], "6.3 16.7 11.0": ["peopel"], "3.3 12.2 -1.5": ["dissapoint"], "-0.2 7.7 18.8": ["crofts"], "-0.8 13.4 10.0": ["kuch"], "-2.3 16.7 8.8": ["prosocial"], "14.1 5.6 9.9": ["pogoing"], "6.2 1.8 8.4": ["poppet"], "2.1 12.1 17.6": ["softhearted"], "0.4 4.8 3.4": ["floorplanning"], "7.2 9.0 13.1": ["cyanobacterium"], "-0.9 0.7 0.5": ["reasearch"], "11.1 3.0 -1.8": ["tollroad"], "-6.5 21.5 -3.7": ["maulana"], "-5.8 1.4 6.3": ["bereavements"], "0.9 -1.1 13.8": ["haat"], "2.6 10.1 24.3": ["eatable"], "2.0 22.6 3.8": ["occlude"], "-3.7 0.7 13.6": ["songket"], "1.3 2.4 9.7": ["overprinted"], "18.2 8.2 4.1": ["woozily"], "2.1 10.2 -0.6": ["depoliticise"], "-0.2 10.5 -3.4": ["proselytise"], "7.4 9.1 1.3": ["independance"], "1.3 8.6 16.1": ["vera"], "25.1 16.1 15.4": ["lifelessly"], "12.9 11.9 1.4": ["spygate"], "5.3 2.8 14.8": ["jou"], "7.6 10.0 -1.9": ["primarly"], "9.2 15.2 3.6": ["topographies"], "4.3 18.8 6.8": ["temporizing"], "1.1 -0.3 0.1": ["refurnished"], "14.7 10.9 17.1": ["frig"], "3.5 2.8 5.2": ["tournment"], "-2.8 5.2 3.2": ["uncongested"], "3.2 12.0 5.3": ["derisking"], "12.0 10.5 5.4": ["seismographic"], "8.3 8.3 33.0": ["chitterlings"], "10.1 13.4 15.4": ["redoubles"], "-0.2 32.5 4.1": ["lawfare"], "10.6 10.7 20.4": ["swain"], "11.7 12.8 14.1": ["harmlessness"], "-6.6 6.5 14.7": ["euthanizations"], "-8.6 9.2 6.4": ["viremia"], "3.9 39.2 12.6": ["reconnoiter"], "-1.4 -2.4 -0.1": ["lyceum"], "5.6 5.1 1.7": ["fracked"], "4.0 11.1 15.7": ["bedliner"], "3.5 -0.2 8.6": ["pannier"], "6.5 4.5 4.6": ["contrastingly"], "6.4 10.6 13.9": ["canyoneering"], "-6.2 0.2 -1.6": ["decisons"], "7.1 7.1 19.5": ["intarsia"], "9.9 15.7 11.9": ["hernews"], "22.8 6.2 8.0": ["flatscreens"], "4.9 1.2 3.5": ["amortise"], "15.7 9.3 9.4": ["footpads"], "11.4 12.1 16.5": ["brollies"], "-3.3 5.7 -0.9": ["liasion"], "3.9 14.2 6.3": ["monetarists"], "2.7 6.3 9.3": ["reall"], "3.0 8.3 9.8": ["clientelism"], "3.2 5.3 -0.1": ["sublicensees"], "-0.5 5.4 20.9": ["liftboat"], "4.3 8.2 23.6": ["ferryboats"], "-4.9 11.4 1.3": ["renunciations"], "13.8 16.9 15.4": ["outcompeted"], "14.1 9.4 11.9": ["chor"], "6.5 -4.2 9.7": ["mysql"], "6.7 -5.2 0.8": ["busked"], "23.0 21.9 14.8": ["steamrollers"], "3.6 2.6 43.8": ["seining"], "2.4 4.4 16.4": ["wafering"], "13.1 8.4 6.4": ["phile"], "2.4 -2.5 4.5": ["mba"], "-0.2 10.7 7.7": ["sabermetricians"], "-2.2 11.1 5.3": ["chieftainship"], "7.7 -1.4 1.2": ["auditoria"], "21.8 7.1 5.4": ["conking"], "15.8 0.4 14.1": ["liquified"], "4.7 16.2 15.6": ["pleasantry"], "4.8 13.7 10.4": ["hedger"], "0.9 4.9 16.6": ["wakeskate"], "8.8 13.2 6.5": ["gamepads"], "2.3 17.9 0.3": ["riposted"], "11.4 21.4 8.4": ["illumined"], "2.5 3.2 -2.3": ["genotoxicity"], "0.4 12.3 4.9": ["covalent"], "7.2 18.4 13.6": ["scabbing"], "8.2 9.7 7.2": ["orkut"], "7.4 27.6 9.0": ["panderer"], "10.5 2.1 1.9": ["mimeographed"], "-0.9 1.3 17.5": ["snowcoach"], "-3.9 14.3 -3.2": ["misrepresentative"], "2.6 7.0 12.3": ["loosie"], "-3.5 18.2 9.0": ["assimilationist"], "3.4 13.4 21.3": ["pitta"], "7.4 10.8 8.8": ["blemishing"], "-1.0 11.6 1.7": ["maulvis"], "13.6 12.7 26.8": ["sheeps"], "26.5 4.9 7.6": ["suppler"], "2.9 6.8 16.3": ["despondence"], "2.2 6.2 5.0": ["oin"], "0.6 15.6 9.4": ["mishits"], "-3.0 11.4 4.9": ["gearshifts"], "12.7 12.6 6.0": ["unclenched"], "6.6 7.2 46.6": ["geoducks"], "1.3 9.3 6.6": ["agood"], "8.4 5.5 4.2": ["neue"], "6.4 7.6 21.0": ["carabaos"], "3.8 10.3 4.8": ["superintending"], "0.9 20.1 5.1": ["processionists"], "10.9 11.2 3.6": ["charkha"], "9.3 20.5 14.8": ["grumblers"], "9.4 17.2 5.6": ["sbox"], "-3.9 13.9 10.0": ["centerfielders"], "-5.3 10.0 2.9": ["undiscussed"], "6.0 10.6 8.0": ["src"], "6.8 1.1 11.0": ["bellmen"], "5.6 5.5 3.6": ["neuroscientific"], "17.0 27.2 11.1": ["tauntingly"], "6.1 28.9 2.7": ["jetfighters"], "24.6 12.9 7.3": ["swooshes"], "8.0 2.3 -2.5": ["hig"], "8.6 1.4 8.0": ["donna"], "5.1 10.0 5.2": ["bla"], "5.4 8.4 1.2": ["hardfought"], "7.0 10.6 31.0": ["parboiled"], "7.9 7.4 3.9": ["norteno"], "5.6 5.2 16.5": ["gelateria"], "0.3 6.2 11.3": ["marla"], "9.0 2.0 6.7": ["curtsied"], "4.3 21.3 11.0": ["lunkhead"], "1.8 8.1 7.3": ["overdrove"], "6.6 6.0 1.4": ["comingled"], "4.5 21.6 7.8": ["slaveowners"], "3.9 0.2 29.0": ["jadeite"], "1.2 6.3 9.1": ["iambic"], "0.0 -4.1 6.0": ["sj"], "4.9 20.4 10.1": ["commonweal"], "12.0 -0.2 8.7": ["swathing"], "23.1 14.3 16.6": ["agrichemicals"], "13.8 -2.5 12.5": ["choo"], "-0.2 -3.8 11.5": ["cally"], "8.5 -4.4 17.2": ["polytech"], "5.9 8.9 -0.1": ["channelising"], "7.6 10.8 7.0": ["boisterousness"], "18.2 10.7 22.3": ["diablo"], "10.5 9.1 22.9": ["coattail"], "-1.6 18.8 6.7": ["describable"], "-2.2 11.2 12.7": ["giallo"], "10.6 14.4 16.9": ["argh"], "5.8 8.6 -3.1": ["unauthorisedly"], "13.6 1.2 -11.1": ["arvato"], "3.5 8.1 18.5": ["dabba"], "17.4 17.5 29.8": ["racoons"], "-1.0 8.4 6.1": ["pompey"], "7.7 0.7 8.2": ["koozies"], "9.3 21.2 9.2": ["sorrowing"], "20.6 -5.5 0.4": ["backflipped"], "4.2 5.7 3.0": ["anthropometric"], "11.5 9.1 15.4": ["voluptuousness"], "9.1 13.5 5.4": ["whinges"], "3.6 5.0 11.8": ["mtrs"], "8.0 10.7 13.8": ["communitarianism"], "3.6 7.5 49.6": ["seiners"], "12.9 5.6 15.6": ["glom"], "-0.1 3.1 2.4": ["acount"], "10.4 9.6 18.3": ["farthing"], "5.7 4.8 6.0": ["guilted"], "8.4 17.0 7.1": ["unbuckling"], "0.8 1.2 7.6": ["companyinfo"], "8.1 7.8 2.5": ["penpal"], "22.7 28.3 12.0": ["popgun"], "6.7 18.8 15.1": ["norther"], "0.6 2.6 17.8": ["trabaho"], "26.8 5.0 9.1": ["megamergers"], "-3.3 17.1 -2.3": ["unflappability"], "3.5 0.1 3.7": ["trolleybus"], "-7.7 15.9 14.0": ["knuckleballers"], "-4.6 5.2 14.0": ["fords"], "6.2 0.4 20.3": ["handysize"], "-2.2 4.7 12.4": ["brakemen"], "15.5 13.3 4.3": ["steamrollering"], "-8.9 11.1 15.9": ["pseudorabies"], "2.4 2.8 -1.6": ["hich"], "-10.1 4.2 5.7": ["atypicals"], "-3.1 7.5 7.3": ["moisturised"], "14.3 11.4 9.5": ["lewdly"], "18.0 5.4 -0.1": ["ingestible"], "-3.3 3.4 3.3": ["gasolene"], "8.0 9.0 -0.2": ["vez"], "5.9 -1.1 8.2": ["petcoke"], "10.5 3.3 40.2": ["callaloo"], "15.8 5.3 14.9": ["flippy"], "5.0 26.5 3.9": ["superficialities"], "9.4 10.8 18.0": ["bosh"], "8.1 0.6 11.7": ["paintable"], "5.3 1.1 28.7": ["amphorae"], "8.5 16.7 17.6": ["unknowledgeable"], "-5.1 35.5 7.2": ["gametypes"], "24.5 10.3 7.7": ["yoking"], "8.5 1.9 5.8": ["agencys"], "3.3 1.2 6.7": ["doxo"], "-2.5 -5.0 19.7": ["lynn"], "11.5 8.9 9.4": ["preordering"], "0.9 6.3 4.3": ["gemological"], "3.1 4.6 14.1": ["haematite"], "5.3 5.7 9.0": ["acro"], "7.5 -3.2 1.5": ["tohelp"], "-0.5 17.8 7.0": ["minable"], "-4.2 12.3 0.5": ["outdrove"], "2.4 4.9 7.6": ["erionite"], "10.7 13.1 12.8": ["ziplines"], "13.6 3.4 13.8": ["entrepeneurs"], "3.0 7.4 8.4": ["shlock"], "1.7 22.0 13.3": ["sojourner"], "11.2 1.2 8.5": ["twanged"], "-6.1 10.4 3.7": ["posessions"], "9.8 10.2 15.8": ["dauphin"], "5.1 19.1 16.0": ["volleyers"], "7.7 -2.8 14.5": ["mandrax"], "2.2 8.2 10.3": ["chaffed"], "-4.8 7.5 1.2": ["depegging"], "11.6 8.1 7.0": ["ged"], "-2.3 6.9 8.3": ["unconscionability"], "7.3 6.2 14.4": ["indole"], "4.5 13.6 2.8": ["becuse"], "9.9 3.0 14.3": ["charro"], "2.1 1.0 18.3": ["marmalades"], "-2.1 3.5 3.0": ["homeworking"], "3.2 30.7 13.4": ["unforgiveness"], "-7.0 0.8 1.6": ["ketoacidosis"], "-1.0 9.7 6.5": ["proscriptive"], "-0.5 1.7 19.4": ["makan"], "0.5 1.1 6.0": ["reformatories"], "11.5 30.6 15.1": ["ariel"], "11.1 12.5 9.4": ["viewport"], "-3.3 11.0 8.0": ["scaphoid"], "6.7 0.3 3.7": ["legalises"], "-13.2 14.5 6.9": ["aggravators"], "2.2 0.2 2.2": ["unprocedural"], "3.2 12.1 8.9": ["cadherin"], "-1.0 8.7 11.6": ["tetracyclines"], "10.6 5.2 8.8": ["portaloos"], "3.3 18.9 14.3": ["substratum"], "-0.9 -0.1 20.9": ["sawlog"], "9.0 7.2 14.9": ["philosophising"], "-4.3 2.3 10.4": ["trapezius"], "0.2 7.3 15.5": ["kerry"], "-2.9 9.8 4.1": ["gravamen"], "4.0 1.3 15.3": ["balikbayan"], "18.2 12.1 15.2": ["gees"], "10.7 9.1 22.2": ["woodblocks"], "2.2 14.0 22.9": ["uncaught"], "7.6 -0.8 2.7": ["valeting"], "-1.0 12.2 9.3": ["inequitably"], "5.0 18.6 3.7": ["culpably"], "1.7 0.6 3.1": ["tapentadol"], "-3.0 16.1 12.3": ["subheads"], "-0.5 3.5 7.3": ["clockings"], "-0.3 15.2 3.3": ["becomming"], "10.2 14.8 11.3": ["steepling"], "13.0 5.6 3.6": ["bemusedly"], "9.5 1.9 2.1": ["buddied"], "12.3 16.8 11.0": ["whitehouse"], "26.2 11.9 16.7": ["galumphing"], "3.0 7.3 -1.5": ["explainers"], "12.0 -6.6 5.3": ["tizz"], "15.4 13.6 4.8": ["makeweights"], "10.5 6.1 35.6": ["wigeon"], "-7.5 6.9 2.0": ["autoloaders"], "-0.4 3.5 8.4": ["curies"], "15.4 6.8 11.4": ["phrenology"], "20.7 11.8 11.1": ["adland"], "-0.1 5.0 -0.6": ["returing"], "9.9 23.2 11.1": ["neutralizer"], "6.4 4.1 2.1": ["soit"], "-2.5 14.6 10.3": ["unremorseful"], "2.7 15.2 16.3": ["tellings"], "2.0 24.6 -2.2": ["antifascist"], "10.6 5.4 16.5": ["camomile"], "11.7 13.5 12.5": ["stickin"], "4.1 0.3 -0.0": ["unabsorbed"], "11.4 6.1 6.1": ["inthemix"], "3.6 7.6 10.1": ["mountainbiking"], "-1.3 14.6 8.1": ["centrebacks"], "8.6 7.1 12.0": ["hardwearing"], "14.7 13.5 11.4": ["mutha"], "-1.4 6.7 9.4": ["dieldrin"], "3.5 8.9 0.9": ["contine"], "1.8 18.2 6.2": ["baseness"], "8.4 23.5 13.2": ["swordfighting"], "2.7 2.8 30.0": ["otoliths"], "-7.0 14.8 12.2": ["reoccurs"], "2.3 4.3 3.1": ["thermoelectrics"], "0.7 2.4 19.6": ["bartend"], "10.0 10.8 18.5": ["dishcloth"], "-4.2 5.2 2.0": ["imprest"], "4.5 16.1 21.4": ["woodpiles"], "4.6 3.7 6.8": ["sensorimotor"], "5.3 3.3 9.1": ["tocotrienols"], "7.4 9.6 36.0": ["juglines"], "7.7 -0.1 7.1": ["whistlestop"], "5.7 30.8 9.6": ["retributions"], "5.9 17.6 11.2": ["occultist"], "7.9 8.3 25.8": ["vada"], "15.2 2.7 16.2": ["boccie"], "9.8 -0.9 -0.1": ["accoring"], "5.8 11.6 10.2": ["greyed"], "3.9 -1.1 7.3": ["smoothening"], "0.4 8.2 14.3": ["rhesus"], "7.2 18.3 6.3": ["banes"], "9.5 13.0 14.3": ["baaaack"], "4.2 14.9 12.7": ["komusubi"], "7.9 4.1 19.8": ["dau"], "24.0 8.6 27.2": ["blancmange"], "4.9 23.9 8.3": ["liminal"], "9.5 10.4 16.3": ["rippin"], "1.7 32.8 1.7": ["warzones"], "-3.7 0.7 11.7": ["leachable"], "14.1 2.0 12.7": ["lutes"], "11.7 13.0 4.8": ["greaseboard"], "-3.6 12.3 16.3": ["fanservice"], "-1.5 5.5 2.7": ["transcodes"], "11.7 6.4 24.9": ["harborfront"], "3.3 11.5 5.7": ["distortive"], "4.7 2.0 -0.4": ["misdialed"], "1.1 13.5 10.7": ["kiya"], "-1.2 2.2 7.6": ["planholders"], "8.7 11.4 1.5": ["kidnaped"], "5.4 5.8 9.0": ["drusen"], "22.7 9.8 16.7": ["toreador"], "-0.7 4.4 4.4": ["masterplans"], "4.9 15.8 5.0": ["condescends"], "17.0 15.8 15.3": ["lasciviously"], "14.5 15.1 9.0": ["crimefighters"], "13.9 17.5 4.8": ["uncharitably"], "13.5 9.7 13.4": ["camelback"], "9.7 15.3 12.7": ["clunks"], "8.3 8.0 5.7": ["bagless"], "20.2 8.2 17.0": ["ropy"], "20.0 10.2 11.1": ["beefiest"], "-5.3 9.0 3.1": ["birthparents"], "3.1 21.9 12.3": ["misdirections"], "-0.2 10.0 1.1": ["milliamps"], "8.0 7.6 28.7": ["areca"], "-0.5 4.1 -1.0": ["oppurtunities"], "15.1 27.1 21.1": ["wookie"], "-8.1 1.6 1.4": ["approvability"], "14.0 21.6 13.8": ["torquing"], "6.8 9.6 7.9": ["kewl"], "4.0 -4.5 7.2": ["anni"], "18.0 10.3 31.2": ["chalupa"], "0.3 4.6 11.1": ["multicamera"], "17.9 1.0 21.0": ["quacked"], "7.9 4.6 11.8": ["cels"], "11.5 14.6 5.9": ["strongarm"], "7.9 10.9 17.9": ["curdles"], "-2.4 5.4 0.2": ["writen"], "2.2 4.8 5.8": ["terabecquerels"], "-3.3 6.1 8.3": ["truanting"], "22.7 9.9 6.3": ["shambled"], "-7.4 5.8 3.1": ["reprioritise"], "-1.6 15.8 4.7": ["eulogist"], "15.4 6.6 18.4": ["russell"], "9.9 15.2 7.1": ["presumptuously"], "-3.3 19.0 8.5": ["transitive"], "8.6 0.1 6.4": ["hace"], "-3.6 10.8 8.4": ["communties"], "-3.2 9.1 4.1": ["actuations"], "2.6 12.5 -0.2": ["universalization"], "13.5 11.2 17.8": ["furling"], "5.3 19.4 20.4": ["scalawag"], "7.2 22.4 6.7": ["counterexample"], "2.4 5.5 0.2": ["misrouted"], "-5.8 12.6 11.6": ["granulocytes"], "1.8 13.8 6.7": ["parasympathetic"], "-2.8 4.1 8.9": ["patellar"], "1.5 18.7 -0.4": ["inoculates"], "3.5 4.7 13.2": ["guk"], "-14.4 7.2 2.6": ["enterings"], "4.5 -2.1 -0.3": ["renowed"], "20.9 7.3 20.9": ["knothole"], "-4.8 7.2 -1.0": ["reccomend"], "15.1 14.1 4.2": ["gunmaker"], "-5.4 4.6 2.8": ["tipranavir"], "15.1 15.6 16.1": ["submarining"], "8.3 6.7 10.7": ["pearler"], "5.2 11.5 8.2": ["chillax"], "4.2 14.6 3.7": ["gimped"], "-1.8 5.7 15.1": ["liqour"], "7.6 18.9 5.9": ["endearments"], "1.8 16.7 5.2": ["prana"], "-3.5 16.7 10.4": ["slotbacks"], "5.6 11.9 -1.6": ["fames"], "6.1 23.8 1.2": ["bivouacked"], "8.9 14.3 12.4": ["stepover"], "5.7 3.4 2.9": ["stablize"], "20.7 1.8 6.7": ["barfed"], "9.0 7.5 7.5": ["vetters"], "9.0 24.2 8.5": ["neigbours"], "-5.0 4.8 12.4": ["histologically"], "-1.3 -4.4 22.2": ["ipe"], "15.9 12.0 23.5": ["bonce"], "15.3 0.1 1.9": ["mailshot"], "-0.3 20.0 4.6": ["gamebreakers"], "-4.2 13.2 5.9": ["brostallicin"], "16.1 13.8 12.7": ["coquettishly"], "-0.9 -4.4 -0.1": ["quadruplet"], "16.3 10.5 22.4": ["eucalypt"], "1.2 3.6 47.7": ["blackmouth"], "12.3 13.8 19.8": ["pirogues"], "10.7 4.9 15.1": ["harpsichords"], "2.7 11.6 8.0": ["captian"], "3.6 1.2 14.2": ["rigamarole"], "0.9 8.6 14.1": ["neovascularization"], "-1.2 30.1 1.9": ["warmaking"], "10.0 10.3 19.3": ["mottling"], "8.1 12.9 21.1": ["bate"], "20.4 21.1 13.8": ["indestructibility"], "12.1 -1.9 5.1": ["gl"], "6.5 11.1 26.8": ["dahi"], "10.5 20.1 18.1": ["forrest"], "-8.5 4.8 6.9": ["tocopherol"], "10.2 0.2 35.6": ["stilton"], "6.9 7.9 7.1": ["carlike"], "3.5 3.7 11.1": ["racecard"], "2.5 4.4 11.8": ["hiv"], "3.5 16.5 7.7": ["transhumanism"], "5.0 17.2 5.2": ["certianly"], "7.1 20.9 7.7": ["transmuting"], "8.6 7.8 21.7": ["bairns"], "3.5 18.7 4.1": ["unholstered"], "1.5 3.7 3.6": ["reuptake"], "-1.4 4.4 14.0": ["cellared"], "5.1 35.2 8.5": ["disbeliever"], "8.0 1.1 8.2": ["mille"], "1.6 7.6 2.0": ["beggining"], "20.6 12.3 25.0": ["veiny"], "12.5 2.4 6.0": ["mailshots"], "-2.1 -1.3 12.5": ["lyophilization"], "-1.6 10.8 -0.4": ["becouse"], "-0.5 -0.4 6.3": ["copyediting"], "-6.2 9.8 8.0": ["roundedness"], "8.8 -4.3 15.5": ["jazzercise"], "5.5 -0.4 5.2": ["furnitures"], "28.2 14.7 16.9": ["legos"], "8.5 14.2 4.0": ["autofill"], "-0.9 12.1 19.2": ["overseeded"], "4.8 14.0 5.2": ["evergreening"], "16.8 11.4 12.7": ["yodels"], "-3.6 17.6 9.8": ["vacillations"], "6.7 18.7 17.0": ["hyperpartisan"], "6.1 27.5 15.0": ["saltcedar"], "17.6 3.4 17.0": ["craptacular"], "16.5 31.2 6.4": ["archnemesis"], "16.0 19.0 11.6": ["undiscriminating"], "8.3 4.9 10.2": ["oof"], "17.3 1.9 8.3": ["sties"], "-4.5 14.2 1.2": ["hierarchs"], "2.5 5.3 7.7": ["usr"], "8.2 5.6 13.5": ["stargaze"], "9.1 -2.6 4.3": ["goahead"], "1.8 9.3 1.8": ["spectatorship"], "8.8 6.0 9.2": ["yest"], "4.9 5.6 3.2": ["contre"], "-3.0 7.4 -2.5": ["combustibility"], "-0.1 13.1 -2.2": ["arrogating"], "-1.5 -1.9 -0.2": ["biofilters"], "2.2 -0.5 9.5": ["whiteners"], "-9.0 -2.6 2.1": ["nortriptyline"], "-3.7 3.0 2.7": ["removability"], "-0.1 8.5 7.7": ["pentathlete"], "14.6 10.3 1.5": ["aire"], "11.7 7.2 30.4": ["pohutukawa"], "6.7 4.8 2.5": ["romancer"], "9.6 15.9 13.9": ["appreciator"], "6.2 20.6 11.5": ["comprador"], "19.2 17.4 4.3": ["giantkillers"], "0.9 11.9 10.9": ["outswing"], "12.8 8.2 3.3": ["supercharges"], "-4.4 11.1 3.3": ["prevelant"], "-8.3 0.3 8.7": ["romiplostim"], "6.3 14.6 7.2": ["regen"], "9.5 7.1 22.9": ["papillon"], "8.0 12.4 9.5": ["subcultural"], "10.6 5.0 7.1": ["unexcited"], "17.5 3.9 14.0": ["hizzoner"], "6.5 8.3 14.5": ["downleg"], "10.0 9.1 12.6": ["smalltime"], "2.3 -4.8 5.4": ["ym"], "12.6 5.0 -1.6": ["comback"], "12.4 16.9 8.4": ["spuriously"], "8.3 11.7 25.3": ["xiao"], "1.9 2.9 11.6": ["fretless"], "18.2 23.2 16.2": ["bestiary"], "4.3 5.9 27.6": ["rugelach"], "9.0 17.2 5.8": ["wayfarers"], "11.5 4.8 24.9": ["platefuls"], "6.5 12.2 12.7": ["niggaz"], "-0.9 15.5 6.6": ["reasonings"], "12.7 18.6 6.2": ["flaks"], "-1.2 15.9 6.9": ["forebearers"], "0.9 -4.0 10.0": ["colonics"], "-4.7 5.4 4.3": ["sangat"], "1.6 13.7 8.8": ["glomeruli"], "0.7 8.6 9.2": ["cutups"], "16.2 11.0 13.5": ["unclip"], "-3.2 8.5 14.4": ["organophosphate"], "8.7 5.7 -0.5": ["retrains"], "4.6 2.3 6.2": ["forme"], "21.2 5.7 11.0": ["dolefully"], "6.7 10.1 7.7": ["dunzo"], "8.9 13.1 30.1": ["chokecherry"], "3.6 3.2 -1.2": ["biocatalysis"], "7.6 -0.0 17.7": ["millwrights"], "11.0 14.4 10.0": ["sheathe"], "2.0 4.6 5.5": ["remoting"], "4.0 8.4 8.9": ["dhobi"], "-0.8 5.1 15.5": ["cfr"], "7.6 3.3 9.2": ["ris"], "11.4 -4.1 21.1": ["punnets"], "4.0 6.7 14.4": ["choli"], "9.1 17.3 22.4": ["coqui"], "7.3 11.8 9.9": ["ringless"], "12.5 1.3 15.7": ["longhair"], "13.3 15.5 14.8": ["luchador"], "16.0 4.0 36.6": ["mudflat"], "1.0 1.1 0.2": ["theyear"], "15.9 14.2 21.7": ["palisade"], "8.6 11.9 6.2": ["spectrally"], "9.7 5.2 20.9": ["adams"], "0.5 2.2 11.5": ["boatlift"], "-3.7 11.2 3.3": ["leat"], "0.6 8.6 3.2": ["olice"], "11.0 9.3 5.4": ["admen"], "-10.8 4.0 -2.2": ["nebulized"], "1.7 28.2 0.1": ["negativities"], "10.7 8.8 -1.6": ["ouside"], "0.5 19.5 5.6": ["elliptically"], "11.9 -6.8 18.0": ["grindings"], "-4.8 13.3 0.6": ["ghettoisation"], "9.4 2.5 9.1": ["oper"], "-2.5 2.8 4.6": ["overdrew"], "4.0 9.7 4.7": ["tcfe"], "11.5 5.9 10.9": ["exhibs"], "4.8 6.8 3.1": ["readin"], "1.8 24.4 6.5": ["feudals"], "14.6 27.9 10.9": ["bombsite"], "8.0 18.1 26.8": ["quolls"], "-0.4 -1.4 3.0": ["docus"], "-0.6 5.4 7.2": ["quadratic"], "4.3 3.9 11.1": ["superstock"], "10.3 9.5 5.5": ["multicomponent"], "3.2 7.4 16.7": ["anthropoids"], "9.7 6.1 23.7": ["coffeecake"], "6.5 -2.0 14.6": ["prepster"], "19.4 28.0 21.3": ["swatter"], "9.3 12.0 26.0": ["blueness"], "11.2 4.1 8.2": ["photofit"], "3.5 0.9 5.2": ["underbidder"], "8.7 5.4 14.7": ["shingling"], "1.4 10.6 39.5": ["spearers"], "11.8 13.4 10.2": ["collectivized"], "0.3 8.9 9.5": ["virtuosi"], "2.9 1.1 8.3": ["aj"], "-4.4 7.1 -0.4": ["nicotinamide"], "6.6 15.1 -2.4": ["dumbed"], "13.6 5.6 16.6": ["upswept", "metallophones"], "3.6 9.4 0.8": ["teargassed"], "5.0 -2.0 17.5": ["ontario"], "1.2 24.0 2.2": ["manouevre"], "-3.2 14.9 1.5": ["sanctionable"], "4.3 10.9 7.9": ["inexpressive"], "15.0 8.9 10.3": ["balalaika"], "2.7 7.4 6.7": ["vedic"], "7.2 8.9 11.4": ["powerlooms"], "-3.7 13.0 6.5": ["councilorship"], "7.6 4.4 7.6": ["euphonious"], "7.2 14.5 3.1": ["bolding"], "15.9 5.3 28.0": ["lunchers"], "4.8 9.9 9.6": ["popularizer"], "-2.1 16.0 11.4": ["lumad"], "12.8 13.9 12.5": ["hardpan"], "14.6 13.3 4.7": ["clunkiness"], "6.0 18.5 7.9": ["outworn"], "3.0 1.5 9.3": ["auberge"], "-0.6 18.3 4.9": ["confabulation"], "17.0 11.7 11.8": ["pentagonal"], "-0.4 12.9 5.2": ["cinegoers"], "-9.8 5.1 8.0": ["sv"], "13.1 9.7 15.5": ["jandals"], "4.2 6.2 7.9": ["greenkeepers"], "12.5 17.4 5.8": ["oppn"], "1.9 6.4 11.2": ["ari"], "8.5 11.3 17.8": ["cryosphere"], "3.1 17.3 8.2": ["hashmark"], "1.1 -1.6 0.2": ["runnning"], "21.1 23.7 16.4": ["interloping"], "5.9 16.0 9.9": ["illest"], "-6.7 -4.0 4.5": ["commty"], "8.6 16.6 2.4": ["coutry"], "9.7 15.4 5.4": ["bewailing"], "3.3 0.7 2.5": ["datacard"], "8.1 17.4 10.8": ["fink"], "7.1 15.2 17.0": ["luff"], "11.5 15.8 15.5": ["bushveld"], "-1.4 6.8 7.8": ["sitios"], "15.7 2.8 23.8": ["mislabelling"], "2.8 13.4 10.9": ["talabostat"], "-10.3 9.9 4.0": ["halakhic"], "11.1 15.0 23.9": ["skylark"], "-0.8 0.9 5.7": ["masterbatches"], "-11.5 46.3 2.4": ["counterinsurgent"], "3.6 4.4 3.2": ["recommender"], "5.2 8.1 36.8": ["stoneflies"], "0.6 8.4 22.3": ["heartwood"], "5.1 19.1 -5.4": ["deicide"], "7.9 -3.2 -1.9": ["trolleybuses"], "3.4 10.6 19.7": ["bul"], "-2.8 15.9 33.1": ["furbearer"], "-0.9 5.3 9.4": ["jazzers"], "5.8 -2.8 0.1": ["stinted"], "19.1 19.7 8.8": ["neanderthals"], "13.0 11.5 11.4": ["telestrator"], "-1.2 10.1 15.3": ["osmium"], "13.6 -0.8 8.7": ["soundtracking"], "15.1 5.6 1.7": ["ficticious"], "20.3 5.5 16.8": ["farfromthinkin"], "5.1 7.1 13.4": ["dreamweaver"], "-2.4 3.1 -3.5": ["depature"], "3.7 13.0 4.5": ["chowkidar"], "8.4 16.0 9.2": ["loiters"], "7.4 6.1 14.2": ["ambers"], "7.9 1.5 10.7": ["frocked"], "4.3 7.7 12.0": ["carolling"], "4.7 7.6 14.1": ["chatfest"], "0.2 5.0 10.6": ["racewalking"], "5.1 -3.7 14.0": ["gus"], "-0.6 16.7 9.3": ["crawlspaces"], "-1.7 13.6 0.4": ["auxillary"], "3.6 16.9 13.5": ["inswing"], "-0.4 5.0 24.3": ["matooke"], "13.8 6.1 8.4": ["keygen"], "17.4 10.3 20.9": ["chocs"], "15.2 3.1 21.8": ["protea"], "-1.0 18.5 9.6": ["moaner"], "12.2 0.8 14.1": ["poufy"], "8.4 13.4 7.1": ["perspired"], "-2.2 15.2 11.3": ["gunsmiths"], "-7.7 8.1 11.8": ["annuitize"], "-2.2 4.6 19.7": ["barong"], "9.7 22.8 6.8": ["homeground"], "-7.4 11.7 7.4": ["unfavorables"], "4.9 14.3 30.3": ["reefing"], "12.2 16.2 11.9": ["intractably"], "-1.4 17.0 0.6": ["apparant"], "-4.0 5.2 -1.0": ["equalises"], "-8.4 13.7 2.1": ["alderperson"], "0.4 5.5 19.9": ["wastewaters"], "9.9 1.8 22.7": ["pipelay"], "-1.5 19.0 7.3": ["prepositioning"], "9.6 22.9 11.2": ["barbwire"], "10.1 -0.1 6.1": ["woodgrain"], "23.2 9.8 17.1": ["megaliths"], "6.0 33.5 15.4": ["sonofabitch"], "3.7 5.2 15.9": ["skool"], "13.0 9.2 15.4": ["adsense"], "6.9 11.5 5.4": ["unenclosed"], "6.8 13.7 4.6": ["predicating"], "3.9 15.2 22.3": ["rootball"], "10.7 15.8 7.7": ["imageries"], "2.9 8.5 8.9": ["wouldve"], "1.0 11.1 9.5": ["atonality"], "5.8 6.4 9.7": ["kelvin"], "14.7 9.0 14.7": ["razzle"], "6.4 4.6 12.4": ["gofers"], "-13.2 2.6 3.9": ["supervisions"], "4.9 8.1 7.0": ["bollixed"], "11.7 9.8 14.3": ["unsalable"], "-10.4 23.2 4.5": ["deployability"], "21.4 5.9 10.2": ["sheikhdom"], "-6.0 1.0 -4.7": ["attestations"], "3.3 3.7 16.6": ["thompson"], "8.3 3.7 9.4": ["ayahuasca"], "17.7 11.8 4.6": ["bigshots"], "4.8 10.2 31.5": ["moult"], "13.1 10.8 24.2": ["katydids"], "-0.2 -1.1 4.3": ["aboutthe"], "-2.0 -4.3 5.2": ["uhn"], "11.8 2.5 3.1": ["holdalls"], "0.1 7.3 2.4": ["transflective"], "0.8 2.9 2.0": ["steamfitter"], "12.3 21.9 6.4": ["asshat"], "6.1 7.8 8.5": ["workingmen"], "-2.4 15.0 4.1": ["retries"], "9.6 9.5 13.5": ["docx"], "9.7 20.7 27.2": ["adelgids"], "1.3 10.0 14.4": ["philip"], "-7.3 8.0 8.9": ["stevens"], "-11.5 11.1 16.4": ["overagers"], "7.1 8.9 5.1": ["prosectors"], "17.0 10.9 17.9": ["daubs"], "3.5 8.2 7.3": ["wast"], "5.1 10.0 24.6": ["asado"], "-0.2 8.0 -0.2": ["wof"], "-1.6 7.3 11.4": ["midspan"], "-5.8 6.3 5.4": ["oversampling"], "5.0 12.3 8.5": ["scoutmasters"], "2.4 10.3 13.7": ["stepkids"], "12.4 3.1 0.1": ["gasifiers"], "21.6 25.5 15.1": ["inkblot"], "8.8 6.9 12.7": ["satta"], "17.9 11.0 14.3": ["facepaint"], "-12.3 3.9 9.2": ["gpd"], "-3.2 15.7 3.1": ["hypoxemia"], "2.7 2.8 5.5": ["appbackr"], "-0.2 10.8 0.8": ["aldehyde"], "1.3 1.1 2.7": ["canbe"], "1.0 36.6 4.5": ["paratroop"], "-1.8 18.9 9.0": ["sovereignists"], "2.0 3.1 1.4": ["cybersafety"], "15.2 13.1 -0.4": ["litigiousness"], "-5.0 9.1 19.0": ["commedia"], "-9.6 3.5 2.8": ["octreotide"], "6.7 10.8 22.5": ["fairgoer"], "18.0 10.9 23.4": ["meltingly"], "-2.9 20.7 3.5": ["interiority"], "0.9 18.5 16.6": ["castling"], "8.8 6.5 20.3": ["groynes"], "0.4 5.2 24.1": ["microbrewers"], "-1.9 9.9 13.1": ["moxibustion"], "13.6 11.3 9.5": ["masonic"], "11.2 21.7 8.5": ["boxcutters"], "6.6 -0.9 7.5": ["rrp"], "1.0 8.8 6.5": ["linearization"], "12.3 1.2 9.2": ["voguish"], "4.7 6.5 4.6": ["outlot"], "8.9 9.4 23.4": ["floatable"], "11.6 15.2 17.4": ["couse"], "3.7 5.8 12.2": ["pyroxenite"], "-2.5 1.6 5.6": ["proline"], "4.2 0.0 39.2": ["muskox"], "-0.1 8.0 1.5": ["boomy"], "6.1 1.6 8.3": ["shoeprint"], "-5.2 8.0 -1.2": ["threepointers"], "3.4 12.7 5.1": ["rightside"], "-7.3 1.7 6.9": ["nonlawyers"], "-2.6 13.8 7.8": ["altruists"], "5.7 7.3 -0.0": ["automations"], "18.9 10.4 18.6": ["sylph"], "-5.4 22.3 6.8": ["havildar"], "9.9 -2.0 16.4": ["smocked"], "12.7 -4.3 9.6": ["beging"], "-0.9 7.5 11.2": ["steeplechasers"], "-5.6 6.0 2.8": ["migraineurs"], "11.2 1.7 5.4": ["landman"], "5.9 20.0 2.3": ["diffcult"], "16.6 15.9 4.1": ["snarkily"], "-3.5 15.2 1.1": ["interpretable"], "5.1 9.2 2.0": ["multiphysics"], "42.5 5.6 9.9": ["megalith"], "5.1 6.5 20.4": ["watersport"], "4.0 15.7 14.9": ["uncrossed"], "-4.9 7.8 2.9": ["streptomycin"], "-1.1 14.1 9.3": ["archaeologically"], "3.5 0.2 6.7": ["zouk"], "1.0 17.9 24.8": ["sinkings"], "-2.4 5.4 3.3": ["harambee"], "5.4 10.3 9.2": ["overstayer"], "8.9 13.8 12.8": ["pyrotechnician"], "5.7 14.4 5.0": ["pdp"], "10.6 8.4 20.1": ["alba"], "4.3 13.2 3.1": ["lienholder"], "0.1 5.8 3.3": ["liveblogged"], "8.7 12.1 -0.7": ["campain"], "-9.3 3.1 7.1": ["timewise"], "16.6 2.6 -0.4": ["opg"], "1.5 0.8 16.7": ["roundwood"], "2.0 2.1 9.2": ["lamin"], "27.9 -0.8 1.2": ["compay"], "6.3 6.7 9.8": ["stim"], "12.0 -3.9 18.5": ["papyri"], "-2.1 -5.8 -6.7": ["confimed"], "5.9 6.0 10.4": ["reallly"], "6.6 -0.2 4.8": ["xwave"], "21.2 15.4 10.6": ["greensward"], "1.5 4.3 2.5": ["rk"], "10.9 3.5 -0.0": ["gestated"], "16.1 15.4 15.8": ["titty"], "4.0 13.5 7.1": ["blockquote"], "3.2 3.1 21.8": ["falsies"], "4.4 11.4 7.4": ["solute"], "1.3 5.8 0.3": ["apolipoprotein", "unbandaged"], "5.6 4.9 10.1": ["parkades"], "4.4 12.1 6.1": ["redenominated"], "8.8 -3.1 14.1": ["silkscreens"], "10.2 14.0 6.0": ["derogatorily"], "-4.1 -3.5 8.1": ["waterpipe"], "5.0 3.9 7.1": ["ribaldry"], "-0.9 10.3 -2.4": ["departmentally"], "16.6 16.3 13.1": ["cockily"], "3.3 10.1 3.4": ["parliment"], "21.5 7.4 5.4": ["tyremaker"], "19.5 7.6 16.3": ["footstools"], "6.7 8.7 10.4": ["nonporous"], "7.2 18.8 15.5": ["methodic"], "-8.8 -14.1 3.6": ["intensives"], "4.9 6.5 5.0": ["collegue"], "17.8 15.3 12.5": ["hobbyhorse"], "4.5 6.8 5.9": ["bupkis"], "2.4 4.3 0.5": ["biphasic"], "8.6 7.6 0.5": ["airhostesses"], "1.3 17.0 13.2": ["phagocytosis"], "-0.6 5.0 7.8": ["tastefulness"], "6.4 24.6 12.1": ["doeth"], "12.5 11.3 23.0": ["boulangerie"], "0.3 7.3 13.7": ["revegetate"], "-1.4 2.3 18.7": ["mycology"], "7.8 6.0 2.5": ["surrended"], "-0.2 1.2 6.1": ["ferrovanadium"], "-2.9 4.3 23.9": ["litchis"], "13.2 12.9 17.5": ["crossbeam"], "5.4 21.0 10.6": ["democractic"], "3.7 6.8 3.5": ["gangmen"], "5.4 15.5 9.8": ["synonymously"], "0.5 22.1 11.1": ["bushwhack"], "0.7 28.1 15.5": ["chimeres"], "6.0 12.6 -0.2": ["peple"], "-3.7 9.4 11.1": ["resampling"], "9.7 2.6 12.4": ["buckskins"], "0.2 4.3 -0.3": ["opthamologist"], "2.1 3.0 11.3": ["coworking"], "5.6 20.1 0.7": ["recompose"], "17.0 18.6 23.5": ["smoosh"], "2.9 6.3 2.9": ["mixups"], "-9.0 13.3 -5.6": ["noncommissioned"], "12.6 15.2 17.1": ["scrounger"], "1.9 4.6 14.8": ["ghatam"], "0.6 1.8 0.2": ["clitoral"], "17.8 18.6 21.1": ["buddha"], "5.5 5.3 12.1": ["pasteurizing"], "11.1 -1.5 15.5": ["tieback"], "0.8 6.8 8.4": ["cleanshaven"], "7.3 18.8 4.6": ["checkmating"], "-5.1 5.6 5.0": ["nomogram"], "-1.6 9.9 3.1": ["gutsier"], "-3.1 0.6 12.7": ["kanilang"], "-5.7 0.9 4.5": ["perphenazine"], "4.3 7.8 15.9": ["sauciness"], "2.1 2.8 14.3": ["drywell"], "7.8 17.0 18.6": ["overpopulate"], "7.0 -2.3 11.6": ["glammy"], "-8.0 10.7 5.8": ["respectfulness"], "12.0 1.4 8.6": ["igus"], "4.8 13.6 6.0": ["politique"], "11.8 19.5 13.3": ["spambot"], "-7.6 9.5 6.5": ["midnights"], "-3.7 14.0 -2.6": ["behooved"], "-2.3 -2.7 16.7": ["solubles"], "2.2 11.4 8.5": ["hemicellulose"], "-8.6 5.5 -2.9": ["coadministered"], "15.7 16.0 15.1": ["entrepot"], "15.0 21.8 7.7": ["imprecations"], "7.4 3.9 8.5": ["ettes"], "10.1 -0.4 18.2": ["offcuts"], "2.0 6.5 10.6": ["electrospinning"], "9.9 7.9 16.3": ["glycan"], "-1.0 16.8 4.7": ["misremembering"], "0.1 4.1 11.8": ["secon"], "1.3 -2.8 11.7": ["smocking"], "8.3 9.8 6.9": ["cuban"], "7.1 7.9 10.7": ["checkins"], "8.3 6.5 13.6": ["bindle"], "18.1 16.6 26.6": ["foxtail"], "-4.3 7.6 3.5": ["tanespimycin"], "11.8 10.2 13.7": ["carl"], "-2.7 1.7 18.0": ["keglers"], "-0.8 34.8 2.8": ["revenging"], "2.5 15.4 19.8": ["decoction"], "5.0 11.8 13.4": ["nerdier"], "0.4 14.4 13.1": ["derringer"], "-3.5 25.1 3.9": ["delegitimise"], "-0.7 0.7 9.8": ["temporaries"], "-3.9 5.4 2.8": ["sanatoriums"], "14.1 23.1 7.2": ["misgovernment"], "-8.2 8.7 6.5": ["cephalexin"], "-1.9 15.9 -1.9": ["maligns"], "7.9 3.4 9.3": ["gaudier"], "11.8 24.8 9.9": ["chemtrails"], "3.8 -5.7 7.1": ["multicity"], "6.4 8.7 16.1": ["dennis"], "8.3 -11.8 7.4": ["biorepository"], "5.3 7.0 13.7": ["electroplated"], "-5.4 14.2 1.2": ["intubate"], "13.2 16.8 11.1": ["waggles"], "15.3 14.3 10.8": ["technobabble"], "6.0 7.5 2.7": ["photocatalytic"], "10.8 12.1 13.4": ["fungo"], "-5.4 6.0 20.5": ["syrahs"], "4.0 3.4 11.6": ["tilde"], "6.4 5.8 12.7": ["schists"], "14.1 10.7 20.1": ["stalactite"], "-4.1 1.2 8.4": ["mammographies"], "15.4 16.2 15.0": ["enfolds"], "1.4 14.5 12.4": ["keane"], "-7.0 1.8 6.6": ["pethidine"], "11.5 7.6 13.1": ["cameron"], "14.7 10.5 -1.0": ["flummoxing"], "7.7 5.7 11.0": ["crossmember"], "13.3 8.2 18.5": ["acacias"], "9.3 2.0 17.2": ["handi"], "1.0 -5.0 5.6": ["seq"], "11.2 4.1 16.0": ["unitards"], "-1.3 9.5 7.4": ["vigourous"], "-5.2 7.7 0.1": ["achievment"], "11.4 18.4 8.7": ["burakumin"], "12.0 4.5 16.5": ["semicon"], "10.1 1.5 8.8": ["rus"], "9.2 13.0 11.8": ["backspace"], "9.3 8.8 32.3": ["teals"], "5.3 0.6 13.3": ["vloggers"], "6.6 22.8 30.3": ["hardtack"], "5.2 5.7 18.8": ["bloodroot"], "15.6 7.9 29.7": ["boule"], "1.2 20.4 10.2": ["choleric"], "8.4 9.4 6.3": ["stomaching"], "13.3 0.1 6.6": ["donde"], "8.9 9.4 17.4": ["vaudevillians"], "11.6 19.7 6.2": ["inauthenticity"], "10.1 8.1 9.0": ["omics"], "1.1 -0.6 9.0": ["hydrocracking"], "10.7 -2.3 13.5": ["transload"], "8.3 -0.2 6.4": ["bioabsorbable"], "1.4 4.9 7.5": ["meagerly"], "-10.8 13.5 4.9": ["methodologically"], "4.0 35.2 7.1": ["ragheads"], "-5.8 2.3 -2.4": ["registrational"], "7.0 -5.9 4.7": ["lated"], "11.4 19.6 13.6": ["knifings"], "2.2 -0.8 6.2": ["deconstructions"], "14.5 -1.4 15.5": ["enka"], "12.0 6.2 0.7": ["overbill"], "11.7 15.0 7.2": ["murkiest"], "1.7 17.6 1.4": ["freemasonry"], "6.6 7.8 5.8": ["polymerisation"], "-8.7 6.9 -1.5": ["acamprosate"], "-3.9 1.8 5.1": ["ves"], "0.8 21.2 -0.9": ["efface"], "-5.0 13.8 8.5": ["nonresponse"], "0.7 10.5 3.5": ["unexceptionable"], "-4.5 8.0 16.8": ["horseplayer"], "4.3 1.4 20.6": ["tok"], "6.6 1.4 16.7": ["stitchery"], "-2.2 -1.3 3.4": ["fith"], "2.8 5.6 1.2": ["servicemarks"], "3.7 9.5 8.1": ["penalization"], "-3.0 8.6 12.4": ["ductal"], "6.1 0.9 -1.4": ["filip"], "-6.4 -1.6 6.4": ["clarinetists"], "12.0 23.1 22.9": ["polecat"], "3.7 7.8 11.2": ["hydralazine"], "14.4 31.1 10.6": ["deathtraps"], "1.6 -3.2 -0.8": ["availabilty"], "-0.7 8.6 11.7": ["chorea"], "6.6 7.2 29.8": ["chilaquiles"], "2.0 24.4 4.1": ["objectivism"], "-2.0 30.9 1.2": ["redeploys"], "16.4 12.9 14.0": ["paradisiacal"], "12.6 -2.7 3.7": ["moderne"], "15.3 9.9 32.2": ["gosling"], "-2.1 10.6 3.2": ["catabolic"], "6.6 3.5 11.8": ["valving"], "0.1 10.6 9.2": ["uptrending"], "-6.3 20.6 1.9": ["hermeneutic"], "10.8 13.3 26.2": ["yachtie"], "12.2 3.4 10.9": ["bagfuls"], "3.8 1.2 7.9": ["dispersals"], "-5.3 5.8 14.0": ["maceration"], "6.5 8.9 12.7": ["sudan"], "17.3 -0.2 12.8": ["poh"], "5.9 9.9 13.2": ["geodesy"], "0.1 -5.3 13.4": ["chiang"], "5.8 6.1 7.5": ["waylaying"], "13.1 29.1 24.9": ["huntress"], "6.2 -2.8 5.8": ["lubricious"], "7.4 8.7 29.1": ["aquarist"], "0.4 7.5 0.7": ["redresses"], "-8.6 1.1 9.6": ["hyaluronidase"], "4.5 12.0 7.2": ["subtractive"], "1.1 1.6 12.3": ["foreskins"], "8.3 1.0 13.3": ["tennessee"], "19.3 24.8 25.9": ["blighters"], "-2.4 4.5 1.5": ["anticholinergics"], "8.0 1.9 9.1": ["tox"], "10.2 2.1 9.7": ["playpark"], "15.3 9.9 12.7": ["nonlife"], "8.8 -4.7 16.5": ["sgd"], "5.7 3.4 44.0": ["bonita"], "-0.8 6.3 9.2": ["reffed"], "-0.5 2.3 3.0": ["palmares"], "-1.2 3.1 14.3": ["homogeneously"], "19.3 33.0 28.1": ["flytrap"], "6.6 5.5 5.5": ["faq"], "10.2 6.3 48.5": ["trevally"], "-4.6 17.2 9.8": ["overcorrecting"], "3.6 16.6 3.1": ["flightpath"], "16.3 5.2 8.9": ["saleslady"], "2.0 9.7 9.8": ["inhalations"], "0.7 -2.9 0.0": ["beamlines"], "5.7 13.8 -1.9": ["reiterations"], "5.5 17.7 15.5": ["chairshot"], "0.4 8.8 9.7": ["paleoclimate"], "-1.3 4.6 -1.1": ["sexted"], "3.6 19.2 -4.0": ["behove"], "13.3 5.9 34.7": ["mizuna"], "9.4 28.0 10.2": ["ditherer"], "1.8 10.4 3.6": ["aquaplaned"], "7.7 16.1 1.1": ["deifying"], "8.6 1.0 12.1": ["malta"], "0.6 4.3 14.8": ["alam"], "-3.8 13.6 8.1": ["subroutine"], "-8.6 5.1 4.9": ["chemoradiotherapy"], "4.3 8.6 18.6": ["dishcloths"], "8.9 18.5 10.8": ["antipodes"], "-13.2 21.3 12.3": ["taskings"], "7.7 17.3 0.2": ["riveter"], "5.5 8.0 7.8": ["ramrodded"], "-0.5 0.2 0.6": ["recapitulated"], "-5.6 2.6 19.5": ["bubblies"], "7.5 10.9 5.2": ["lousier"], "1.0 4.5 39.0": ["pullet"], "1.3 -7.5 12.3": ["giclee"], "3.5 19.0 4.7": ["forded"], "9.2 -1.6 15.3": ["rewrapped"], "22.3 21.5 15.0": ["lazer"], "3.1 4.9 23.8": ["biriyani"], "-2.8 7.8 1.3": ["vitiates"], "5.4 3.6 14.7": ["dabbawalas"], "18.0 1.3 6.6": ["commericial"], "-1.9 10.2 5.6": ["tercentenary", "guarde"], "8.1 14.9 0.1": ["underleveraged"], "2.4 2.1 5.8": ["pramlintide"], "11.8 -1.2 14.1": ["kinkajou"], "6.9 0.3 1.0": ["remeasured"], "3.8 2.7 7.3": ["chrono"], "9.7 0.8 9.7": ["comercial"], "-7.3 8.6 3.5": ["levelheadedness"], "0.8 25.7 1.2": ["everyway"], "3.4 14.8 9.8": ["remoter"], "-6.0 6.8 7.9": ["convexity"], "16.6 5.7 3.7": ["suped"], "7.3 15.1 7.1": ["marketisation"], "-3.7 15.3 1.8": ["lifethreatening"], "1.7 8.8 -0.4": ["appointer"], "13.0 0.6 17.7": ["ecozone"], "-2.8 2.1 9.5": ["ccf"], "14.0 12.4 14.7": ["tracery"], "18.0 22.5 14.0": ["anthropomorphize"], "3.7 6.8 1.1": ["peonage"], "8.5 15.4 22.6": ["yawl"], "15.0 9.0 9.4": ["gubbins"], "-1.4 1.9 3.5": ["scopolamine", "agami"], "12.2 24.0 20.5": ["colonizes"], "10.7 8.1 5.3": ["newpapers"], "-6.8 3.6 1.6": ["catheterizations"], "3.5 13.0 16.3": ["melanogaster"], "5.3 14.1 7.9": ["eugenicists"], "-1.8 4.5 5.4": ["conformability"], "-2.4 17.4 8.8": ["entreats"], "13.4 18.9 27.5": ["mouthparts"], "13.3 15.0 10.3": ["nonce"], "-2.9 13.9 9.8": ["crackhouse"], "8.0 5.5 10.6": ["ajax"], "7.3 12.2 17.5": ["scissoring"], "11.0 8.8 7.2": ["sters"], "0.8 11.8 9.6": ["staphylococcal"], "-8.9 23.2 9.2": ["undercovers"], "9.2 9.4 11.9": ["feminizing"], "10.4 9.4 16.0": ["fossa"], "0.1 2.1 38.5": ["pangasius"], "20.7 6.7 15.9": ["boing"], "8.6 4.4 18.5": ["guestimate"], "7.6 9.1 10.3": ["feistiest"], "16.2 5.7 -1.0": ["televangelism"], "10.8 13.3 13.4": ["oxygenating"], "11.3 -1.0 7.1": ["semipermanent"], "5.3 10.4 32.9": ["pupfish"], "8.0 2.6 9.7": ["freeski"], "2.5 6.5 15.7": ["cuer"], "11.7 13.2 15.2": ["samovar"], "-0.4 20.6 7.7": ["bootlickers"], "13.1 14.9 23.3": ["bountifully"], "6.5 8.7 5.9": ["owen"], "-5.3 16.0 6.8": ["societally"], "-2.0 -3.0 8.5": ["yarded"], "6.1 9.1 15.7": ["causa"], "20.9 8.9 3.5": ["outbids"], "7.2 9.1 11.3": ["swearwords"], "0.1 7.7 13.1": ["bimetallic"], "7.1 13.6 32.0": ["loopers"], "-0.1 10.0 9.5": ["gregariousness"], "15.2 14.4 32.5": ["pincher"], "7.5 1.5 8.8": ["shinguards"], "24.7 6.7 27.2": ["lillies"], "10.7 5.7 24.7": ["mari"], "15.6 6.8 29.4": ["marabou"], "13.2 3.9 10.8": ["stockrooms"], "7.6 11.2 12.9": ["diatreme"], "12.4 9.4 13.2": ["terrycloth"], "11.7 -0.5 11.8": ["loveseats"], "1.5 4.7 19.3": ["unsplit"], "-3.1 20.4 12.6": ["knoweth"], "17.6 7.6 1.5": ["partof"], "1.1 10.2 7.9": ["anonimity"], "3.2 3.3 2.8": ["gw"], "3.0 22.8 11.2": ["restrictionist"], "1.2 5.2 14.8": ["fixie"], "4.8 10.3 11.5": ["spinsterhood"], "-1.5 8.0 3.7": ["chattier"], "0.0 4.0 2.1": ["artier"], "12.9 9.5 15.2": ["voltmeter"], "13.2 1.8 22.3": ["toonies"], "19.4 -5.5 5.4": ["ankled"], "-4.8 9.9 -3.9": ["admissable"], "6.2 8.1 15.0": ["showboats"], "-6.1 1.9 1.2": ["remitter"], "1.4 6.8 3.8": ["commutable"], "11.1 0.8 10.9": ["porte"], "18.5 12.4 16.5": ["inquisitively"], "6.4 -4.6 3.4": ["iolo"], "-13.5 0.1 -0.1": ["availment"], "-4.2 11.0 2.2": ["pyruvate"], "23.6 10.9 9.6": ["unbolt"], "5.8 11.3 12.2": ["ingrown"], "6.3 3.6 22.7": ["nene"], "-9.9 6.2 6.1": ["advisees"], "-5.7 2.3 6.5": ["ponatinib"], "10.7 8.3 10.1": ["microneedle"], "-0.7 10.7 12.8": ["keloids"], "5.4 6.8 7.8": ["affectless"], "8.0 5.7 28.0": ["bulker"], "9.1 10.7 7.0": ["showfloor"], "-5.1 9.6 6.2": ["virologic"], "-6.6 17.5 6.1": ["forebodings"], "11.1 -6.8 7.3": ["mastercard"], "23.0 20.3 13.8": ["whorish"], "3.6 28.5 12.8": ["swiftboat"], "6.6 6.6 3.7": ["photomontages"], "5.0 6.1 15.5": ["hopin"], "13.6 -0.7 17.6": ["masonite"], "2.5 8.2 25.7": ["foodways"], "1.6 15.2 15.1": ["intellectuality"], "-7.2 6.9 -1.6": ["mobilizer"], "2.5 4.8 15.1": ["ght"], "0.5 8.9 7.3": ["unauthentic"], "3.6 7.1 12.6": ["aaron"], "9.1 5.1 25.1": ["sadza"], "2.7 11.9 1.3": ["effused"], "2.3 -0.1 11.4": ["luxuriates"], "11.9 0.0 6.6": ["rachet"], "2.9 11.7 6.8": ["leavin"], "8.9 13.6 15.1": ["shortside"], "2.5 -0.2 7.5": ["endosomes"], "20.9 7.4 23.2": ["royale"], "5.1 9.0 14.6": ["microenvironments"], "0.5 13.8 6.1": ["immutability"], "11.8 18.2 4.0": ["cheney"], "18.5 8.5 11.5": ["technorati"], "-2.2 3.1 18.0": ["dockings"], "-4.4 -3.1 -3.6": ["issed"], "6.8 15.5 17.8": ["wristlock"], "15.3 -3.6 30.1": ["timbale"], "11.8 11.9 16.6": ["gores"], "4.4 -11.8 17.8": ["waitressed"], "4.8 0.1 13.8": ["kura"], "6.6 13.3 3.1": ["knighting"], "5.3 2.4 46.0": ["fishcakes"], "-0.2 8.1 -3.8": ["onesided"], "3.8 11.6 1.3": ["unrevealing"], "-2.9 -6.3 -3.6": ["microfilming"], "10.9 -4.6 9.9": ["boxboard"], "10.3 -0.1 23.5": ["rosa"], "4.8 8.3 32.8": ["foccacia"], "22.7 9.5 19.7": ["woodchipper"], "9.0 9.1 5.1": ["pontificators"], "5.3 16.2 8.5": ["perplexities"], "-4.6 1.5 3.1": ["numberof"], "8.7 20.8 17.0": ["townsmen"], "-2.0 13.5 4.5": ["ameliorative"], "12.2 15.4 9.8": ["regathering"], "-6.1 14.0 4.5": ["photophobia"], "15.1 7.3 14.7": ["armatures"], "0.2 3.7 17.5": ["pera"], "14.7 9.0 13.0": ["radiowaves"], "-1.2 -2.3 17.9": ["hackney"], "10.2 5.1 8.5": ["tarrifs"], "7.2 10.1 8.7": ["malapropism"], "8.8 9.6 23.8": ["gastronome"], "-4.6 4.9 3.2": ["rescreening"], "10.2 15.7 12.4": ["insourced"], "8.1 3.6 2.7": ["rollcall"], "2.7 12.5 7.1": ["unfortunatly"], "20.0 4.7 13.9": ["boytoy"], "6.0 10.7 1.3": ["annd"], "5.7 4.9 -5.0": ["strenghtening"], "-4.5 16.8 7.2": ["aphoristic"], "7.0 12.1 -0.3": ["fathoming"], "-4.6 1.8 18.5": ["oaked"], "-7.7 9.9 6.2": ["unimmunized"], "0.4 2.2 10.8": ["microformats"], "12.3 7.4 8.0": ["conniptions"], "-3.6 8.8 13.7": ["smokier"], "-0.7 9.2 -0.6": ["accessary"], "-1.5 2.1 0.4": ["printability"], "3.0 6.5 13.2": ["prefinished"], "-1.6 5.0 3.1": ["entires"], "-1.1 7.8 12.9": ["oestrogens", "distally"], "5.1 6.1 12.2": ["jd"], "12.9 12.7 9.9": ["anuses"], "6.0 11.0 11.3": ["pyrotechnicians"], "7.5 6.5 24.4": ["baize"], "7.9 8.5 22.4": ["aloes"], "4.8 2.9 1.2": ["pursuade"], "-1.1 2.7 5.5": ["coilovers"], "-1.7 8.6 9.6": ["lahars"], "12.0 3.7 6.8": ["overgenerous"], "-7.0 -0.0 11.0": ["skorts"], "7.4 6.9 41.6": ["bowfin"], "8.5 4.8 11.7": ["indonesia"], "15.0 3.4 22.0": ["towage"], "-5.7 11.9 1.9": ["nonpartisans"], "3.1 8.1 8.3": ["adwords"], "-0.5 18.0 9.5": ["cleary"], "-4.4 4.3 5.4": ["topscoring"], "1.2 -2.1 12.3": ["reapplies"], "12.5 8.9 8.5": ["saucily"], "5.8 2.6 -4.8": ["controvery"], "1.7 8.1 -1.6": ["unbanned"], "1.8 10.3 14.0": ["valtrex"], "-1.3 2.1 6.0": ["buydown"], "3.8 2.7 13.9": ["pati"], "12.6 10.1 10.0": ["calc"], "6.0 8.6 17.2": ["lactic"], "28.6 13.3 8.9": ["neato"], "-2.1 3.2 5.5": ["terbium"], "2.4 5.4 21.4": ["plantlets"], "3.5 23.4 5.1": ["dispicable"], "8.0 6.7 6.0": ["img"], "5.4 11.7 5.4": ["ululation"], "7.6 19.9 10.3": ["infantilized"], "-1.0 8.3 8.8": ["lennon"], "-4.4 15.1 -0.3": ["canidate"], "4.1 14.2 7.6": ["soberness"], "6.7 2.9 15.2": ["corbels"], "6.8 10.7 21.6": ["yuccas"], "1.5 10.3 3.2": ["subtenant"], "10.9 9.1 13.6": ["drumset"], "2.8 2.4 1.2": ["demised"], "-4.3 2.2 5.1": ["unde"], "-1.2 10.8 11.6": ["passholder"], "0.4 2.6 11.9": ["voke"], "1.8 -1.6 3.6": ["ipoque"], "13.8 21.0 10.2": ["macrocosm"], "-3.0 16.6 12.5": ["backtest"], "-0.3 5.9 10.8": ["oropharynx"], "-2.0 7.5 13.4": ["tweezing"], "10.7 3.0 17.3": ["mainlines"], "15.5 14.5 17.5": ["deltoids"], "-0.1 10.6 5.3": ["overscheduling"], "-3.7 14.5 10.5": ["covariance"], "5.0 8.9 4.3": ["blagging"], "12.6 4.2 14.2": ["kickflip"], "-5.0 3.5 16.1": ["lipolysis"], "14.8 8.9 8.3": ["backcloth"], "5.2 1.1 3.4": ["audi"], "13.3 -1.3 17.5": ["grandes"], "17.8 7.5 20.6": ["voile"], "0.1 8.0 2.3": ["emmissions"], "20.5 14.6 12.3": ["chrissakes"], "8.6 11.6 30.9": ["lough"], "4.0 4.6 12.3": ["colorimetric"], "0.2 -0.2 18.1": ["bartended"], "1.8 13.9 6.1": ["situs"], "2.6 1.6 8.8": ["arenacross"], "4.0 5.8 49.3": ["gillnetters"], "0.4 5.4 4.5": ["heighted"], "9.6 15.0 1.8": ["anachronistically"], "4.9 -1.9 13.4": ["agua"], "-6.5 12.3 1.9": ["sahab"], "4.1 11.1 7.3": ["mechanistically"], "3.5 19.8 6.4": ["irrationalities"], "10.6 7.6 5.5": ["hyperlinking"], "-4.8 6.5 11.0": ["ens"], "4.1 3.2 6.0": ["xenograft"], "-3.3 6.2 -3.0": ["misattributed"], "1.8 16.1 13.1": ["drogue"], "-8.9 1.8 -1.8": ["divalproex"], "1.8 15.8 8.9": ["ingathering"], "16.3 12.7 15.7": ["adorableness"], "2.5 20.2 8.3": ["excercises"], "3.5 8.5 3.5": ["thymine"], "14.0 12.0 6.4": ["deigning"], "7.3 5.3 11.2": ["jose"], "12.1 19.2 14.2": ["recolonize"], "-5.4 8.8 8.3": ["satisifed"], "12.1 4.9 23.3": ["boerewors"], "6.2 21.9 12.2": ["replicant"], "7.1 22.1 6.0": ["unintimidated"], "6.2 6.1 18.5": ["powerboating"], "1.5 9.4 15.0": ["housebreak"], "13.7 17.6 17.7": ["chocks"], "15.9 6.2 16.1": ["dweeby"], "10.9 8.8 7.9": ["saas"], "-0.6 5.8 1.0": ["redshifts"], "9.4 15.7 7.7": ["sublimating"], "4.9 -1.4 0.6": ["ihre"], "3.7 16.2 5.9": ["discomfit"], "-9.4 0.9 9.8": ["discectomy"], "-1.6 4.6 14.7": ["elbowroom"], "6.4 13.4 10.6": ["buffaloed"], "-2.4 4.1 4.5": ["nonroster"], "7.8 17.6 14.9": ["shellcode"], "12.9 4.9 30.1": ["napoleon"], "15.8 11.4 11.6": ["roided"], "10.0 15.5 22.8": ["brock"], "8.4 0.9 1.1": ["examing"], "14.7 17.8 8.3": ["vaccuum"], "6.8 5.5 10.9": ["doddery"], "6.9 8.6 34.2": ["sukiyaki"], "12.4 14.8 18.4": ["fakir"], "9.6 1.6 17.4": ["guayabera"], "3.6 -1.2 5.6": ["hyung"], "-0.1 9.9 6.4": ["bickerings"], "1.7 12.3 15.2": ["feverfew"], "20.8 10.7 6.2": ["googol"], "8.4 7.7 7.5": ["debaucherous"], "9.7 15.2 25.5": ["liriope"], "0.2 15.2 -0.7": ["vouchsafed"], "9.7 8.2 14.1": ["oink"], "4.4 -1.3 5.2": ["countys"], "-3.8 1.1 2.1": ["pretreat"], "3.3 11.1 11.1": ["dyscalculia"], "10.8 14.3 26.9": ["bight"], "2.1 4.1 11.6": ["ood"], "-2.8 3.1 4.3": ["psychometrics"], "1.2 22.8 0.4": ["confrontationist"], "-0.4 19.1 7.9": ["administation"], "3.0 7.3 18.5": ["eyebar"], "1.4 5.8 17.5": ["muna"], "16.7 12.4 0.9": ["hotfoot"], "9.3 9.8 33.7": ["meatiness"], "5.3 19.8 11.3": ["charismatics"], "24.1 0.8 0.2": ["shilled"], "8.1 13.7 11.9": ["zed"], "9.2 9.8 16.3": ["lifebelt"], "3.9 14.0 11.9": ["hisself"], "-1.5 5.4 19.2": ["drapey"], "-1.9 18.2 8.1": ["hastiness"], "0.3 9.0 -0.1": ["muder"], "3.9 -5.1 11.8": ["preems"], "0.8 7.2 47.7": ["salmonid"], "4.3 -0.4 8.6": ["perfoming"], "-10.0 4.4 3.9": ["mammographic"], "4.6 20.8 16.8": ["blackwater"], "0.9 21.3 4.2": ["malingerer"], "-2.4 10.6 6.8": ["reactant"], "6.4 6.3 7.8": ["stateliness"], "13.3 6.6 14.2": ["bedposts"], "-1.2 1.4 7.7": ["ori"], "5.1 5.5 16.7": ["angiosperms"], "11.8 -0.7 11.3": ["toped"], "-5.9 16.5 -1.8": ["imputes"], "3.9 19.5 -1.1": ["incongruence"], "16.8 13.6 13.0": ["babel"], "-0.8 7.0 13.0": ["riluzole"], "11.3 -8.1 10.2": ["minibonds"], "2.8 11.9 4.8": ["arry"], "7.3 5.8 0.4": ["videoclips"], "1.7 1.7 16.7": ["daytrips"], "1.7 11.4 23.1": ["hor"], "13.9 10.6 19.1": ["shovelfuls"], "1.3 3.6 11.0": ["batboys"], "0.9 8.2 10.5": ["accentuation"], "-5.6 -1.5 2.3": ["isoflurane"], "2.4 6.7 6.5": ["ofour"], "3.3 12.0 6.9": ["emissivity"], "17.1 12.3 15.5": ["zoomable"], "15.7 6.6 39.0": ["shiso"], "8.8 10.8 10.6": ["roofies"], "8.9 5.9 4.0": ["superfit"], "6.0 4.1 12.9": ["neckerchiefs"], "7.5 12.2 4.1": ["overexposing"], "27.5 7.7 21.4": ["nautilus"], "12.0 5.7 13.0": ["uo"], "-2.8 3.5 8.1": ["herceptin"], "22.1 3.1 6.0": ["heisted"], "-0.3 9.9 13.0": ["consigner"], "5.5 22.5 20.2": ["layline"], "0.4 12.4 12.3": ["ejido"], "21.2 9.4 15.7": ["pictogram"], "7.0 8.3 15.5": ["winnows"], "8.1 13.3 22.9": ["mescal"], "10.1 13.8 10.1": ["grubbered"], "17.4 19.2 16.8": ["bludgers"], "0.9 12.8 0.0": ["valediction"], "7.3 -9.5 5.4": ["cludes"], "11.7 1.3 10.1": ["opulently"], "3.0 10.8 2.1": ["utd"], "4.4 11.7 6.2": ["plurals"], "-0.8 5.3 0.7": ["scandalizing"], "-4.3 7.0 2.0": ["unendorsed"], "9.1 6.6 1.4": ["nobbled"], "5.5 11.1 3.2": ["catcalling"], "7.8 29.4 20.5": ["horcruxes"], "-9.1 9.6 6.2": ["scapular"], "12.4 12.8 2.6": ["altimeters"], "9.0 0.8 20.1": ["yao"], "-11.8 3.4 6.8": ["teammed"], "-8.4 3.2 9.3": ["underproduction"], "-0.2 7.6 12.2": ["calcrete"], "5.1 6.9 8.3": ["illy"], "-3.9 2.2 -4.1": ["snd"], "11.8 8.3 3.0": ["cowtown"], "13.9 12.8 2.6": ["nonsporting"], "-4.5 6.7 2.3": ["recompiling"], "19.8 1.7 13.2": ["ladened"], "3.5 8.2 12.3": ["chromophores"], "-2.1 11.0 1.6": ["alienable"], "-1.4 6.7 8.8": ["ejaculations"], "-4.6 8.0 6.0": ["sata"], "13.2 7.1 25.3": ["fluffiness"], "12.8 8.4 10.6": ["topi"], "-6.0 5.5 8.9": ["resections"], "-2.6 24.2 1.5": ["reprove"], "4.2 1.1 9.7": ["columbia"], "13.6 17.6 9.2": ["bunglers"], "17.4 9.4 17.8": ["minigolf"], "-3.4 -3.3 8.5": ["layette"], "5.0 15.1 7.1": ["sojourning"], "0.9 14.9 13.9": ["chinstraps"], "-7.2 3.6 7.6": ["rectories"], "-0.7 9.2 -1.7": ["notifier"], "-2.1 15.6 6.8": ["darbar"], "11.1 17.2 9.3": ["riderless"], "4.9 5.6 0.2": ["nonutility"], "10.8 -0.2 11.2": ["needlecraft"], "7.9 11.7 39.3": ["bottlenose"], "1.8 4.3 1.3": ["definate"], "6.1 13.6 5.6": ["trully"], "21.2 6.7 13.9": ["processer"], "12.6 5.8 39.3": ["marlins"], "4.5 5.8 7.7": ["homme"], "7.0 3.1 1.0": ["contemporize"], "8.5 13.8 15.5": ["fakeness"], "7.9 13.6 6.8": ["nitpickers"], "17.2 13.0 11.2": ["farmyards"], "7.7 8.5 -0.4": ["repurcussions"], "5.3 14.1 9.5": ["nimbyism"], "15.5 31.4 6.1": ["viscious"], "-3.2 6.9 13.2": ["thse"], "7.4 11.3 35.9": ["pinnipeds"], "6.2 10.8 4.1": ["contagiously"], "18.0 24.9 16.0": ["hoverboard"], "7.9 10.8 4.2": ["bom"], "2.7 4.6 11.3": ["nonsecurity"], "9.7 33.1 9.4": ["bioterrorists"], "-0.3 -4.9 -2.5": ["onhand"], "-2.1 9.2 8.7": ["monovalent"], "13.3 15.7 27.8": ["terrestrials"], "0.8 7.4 7.8": ["discographies"], "-6.2 6.6 2.5": ["saturations"], "-0.0 6.2 2.2": ["powerpop"], "8.9 20.8 10.3": ["chutzpa"], "9.9 37.6 10.9": ["berserker"], "24.4 9.1 19.3": ["bloats"], "8.9 12.1 8.0": ["inspiringly"], "-0.6 5.4 16.7": ["centrosomes"], "-2.4 10.3 4.2": ["glufosfamide"], "3.2 8.7 15.0": ["passback"], "5.2 17.6 8.7": ["bloviate"], "-0.5 21.7 19.6": ["countout"], "3.6 15.4 22.6": ["glucosinolates"], "-2.6 18.6 6.7": ["kidnapers"], "17.4 13.1 5.9": ["klaxon"], "16.6 2.3 4.4": ["lowcost"], "11.0 20.0 12.7": ["jibing"], "19.0 24.5 10.8": ["superhumans"], "0.4 1.8 6.1": ["apprx"], "8.6 11.0 9.7": ["voicebox"], "6.9 3.8 9.6": ["unbooked"], "-7.6 0.7 13.2": ["deaneries"], "0.5 5.0 11.7": ["supernotes"], "0.2 3.6 6.8": ["stented"], "13.8 9.6 11.2": ["sidelong"], "6.2 8.1 7.1": ["hesitatingly"], "-4.0 1.3 19.3": ["capri"], "1.9 4.4 20.0": ["serranos"], "-0.9 17.2 4.6": ["explicating"], "0.5 0.1 16.5": ["nonpresidential"], "3.8 15.9 3.9": ["depegged"], "5.7 -1.7 14.1": ["hada"], "5.4 10.8 8.7": ["leet"], "7.2 14.6 6.3": ["marketcap"], "7.9 6.3 6.2": ["reinsuring"], "4.7 10.6 5.9": ["managable"], "3.7 3.5 9.0": ["alzheimer"], "-3.7 -0.3 13.7": ["kailangan"], "12.2 21.2 6.6": ["monomania"], "4.0 8.7 7.9": ["phonic"], "9.3 10.6 11.5": ["surmounts"], "-3.0 9.2 13.2": ["fourteeners"], "-2.7 8.3 -4.6": ["pretensioners"], "8.8 5.1 13.9": ["sixtysomething"], "1.7 7.4 17.7": ["dismasting"], "11.2 8.3 -2.4": ["filmless"], "1.4 7.1 25.8": ["masur"], "5.5 13.1 13.7": ["affluenza"], "-4.2 16.3 1.1": ["elided"], "-3.9 15.7 4.7": ["kippa"], "15.4 17.9 10.4": ["clumsiest"], "13.7 12.4 14.7": ["biffed"], "4.0 23.0 7.6": ["agroterrorism"], "-4.5 5.6 17.7": ["statebred"], "2.3 4.2 21.6": ["matcha"], "-2.3 13.3 4.1": ["multilateration"], "14.1 2.9 3.9": ["governent"], "8.9 4.6 31.2": ["churrasco"], "6.5 6.4 10.4": ["albendazole"], "10.3 5.1 0.6": ["mopay"], "2.8 18.3 3.9": ["secularised"], "-2.1 7.8 3.7": ["magnetize"], "6.7 9.8 5.3": ["semper"], "-3.8 -3.7 4.8": ["payscale"], "16.7 21.3 20.8": ["carbonite"], "6.2 7.5 2.1": ["commentates"], "5.9 6.1 13.0": ["siltstones"], "13.7 9.5 16.1": ["mulleted"], "-8.4 -3.1 -1.5": ["seropositive"], "8.2 14.6 5.8": ["anc"], "11.1 12.1 24.8": ["blanches"], "0.9 24.3 7.7": ["literalists"], "8.1 12.6 19.9": ["caramelizes"], "7.1 0.7 -2.9": ["overstimulate"], "-1.5 6.6 -0.3": ["addtional"], "12.4 22.4 15.5": ["unfired"], "-0.4 13.9 3.1": ["womanizers"], "1.8 -3.5 -1.9": ["concessioned"], "4.4 2.9 35.6": ["chayote"], "7.4 2.3 5.0": ["overbridges"], "19.7 9.0 27.9": ["haunch"], "10.6 17.5 9.4": ["buggering"], "18.4 6.7 18.1": ["squelchy"], "16.8 -2.0 24.2": ["paillettes"], "-7.4 -0.5 -3.6": ["cangrelor"], "12.7 10.5 4.6": ["incensing"], "17.7 13.2 20.7": ["honker"], "-1.9 4.5 9.0": ["coproducer"], "11.9 7.2 28.1": ["martens"], "21.6 8.3 13.3": ["lightshow"], "0.6 -1.8 -5.1": ["kmpl"], "2.9 9.3 4.7": ["symbolist"], "18.0 10.6 9.1": ["colliders"], "-1.5 5.1 3.5": ["definites"], "8.0 8.6 17.1": ["bridling"], "12.4 14.9 51.0": ["pogies"], "24.7 14.4 2.1": ["zappers"], "15.0 17.9 12.8": ["rapaciousness"], "-0.7 0.8 15.1": ["nar"], "-3.0 -9.9 8.4": ["minium"], "9.0 -7.4 -3.6": ["annouces"], "10.7 -0.1 3.4": ["tbe"], "14.4 5.7 19.9": ["haar"], "2.8 14.8 11.6": ["debaucheries"], "5.8 10.9 20.1": ["heaths"], "14.4 -0.7 2.2": ["multitasks"], "8.0 15.9 20.7": ["etrog"], "20.5 -0.3 10.1": ["engg"], "-0.0 -1.2 5.4": ["thelast"], "12.6 7.7 9.0": ["econobox"], "1.8 4.5 13.4": ["milonga"], "7.3 5.9 30.9": ["rufous"], "4.6 12.1 13.6": ["splines"], "-1.8 9.2 8.9": ["amma"], "-1.5 -1.6 5.0": ["reaggravating"], "-0.6 2.9 4.4": ["dialogued"], "5.8 -7.3 -7.6": ["provid"], "5.6 7.5 10.9": ["briskness"], "-1.7 19.7 -0.7": ["commissariat"], "18.8 12.1 12.0": ["roboticist"], "24.8 16.5 18.7": ["stompin"], "5.4 1.8 12.1": ["barbara"], "0.2 22.0 1.4": ["profanation"], "8.7 7.8 12.3": ["sludges"], "1.7 3.8 0.9": ["nonsports"], "5.0 15.4 10.1": ["scrummagers"], "11.5 -5.0 7.1": ["desde"], "-0.4 20.9 1.3": ["perjurer"], "4.0 -0.7 3.9": ["whle"], "-0.7 14.4 11.5": ["tanods"], "3.1 16.6 13.5": ["bossiness"], "8.1 6.7 5.7": ["rece"], "6.0 7.1 9.8": ["lowpoint"], "10.7 7.6 14.0": ["wastrels"], "3.4 10.0 5.5": ["outpoints"], "3.6 38.1 4.5": ["peshmergas"], "-0.9 4.2 2.4": ["inst"], "11.0 22.3 10.0": ["immoveable"], "13.6 -4.4 5.5": ["recordbreaking"], "10.2 12.5 11.7": ["rads"], "20.2 19.2 16.6": ["scallywags"], "6.6 -1.0 10.6": ["oldtime"], "14.5 12.2 7.1": ["iconically"], "5.5 10.5 8.0": ["warrent"], "7.4 8.6 11.7": ["brandon"], "11.5 10.5 12.0": ["styli"], "8.8 4.1 49.2": ["branzino"], "7.7 10.0 1.8": ["voxels"], "11.1 1.1 9.3": ["dowtown"], "-5.0 6.6 4.2": ["coadjutor"], "7.3 25.6 8.3": ["handballing"], "-0.3 11.3 14.0": ["rajas"], "2.3 14.5 7.6": ["malinvestment"], "6.6 20.6 15.9": ["enziguri"], "2.1 11.7 13.1": ["legspin"], "-1.9 8.6 1.0": ["messrs"], "12.4 13.7 15.7": ["kissy"], "3.4 9.9 5.4": ["hotlist"], "10.9 4.1 16.2": ["whee"], "16.0 10.8 9.8": ["uncaged"], "-6.6 3.1 1.5": ["silodosin"], "-2.4 11.6 11.6": ["tintype"], "7.6 -1.0 10.3": ["dangdut"], "13.1 4.6 13.4": ["crimper"], "14.6 25.7 7.4": ["plunderer"], "13.0 0.6 22.9": ["polytunnel"], "9.7 11.2 17.7": ["wobblers"], "0.6 6.3 9.8": ["thujone", "microinjection", "rotaviruses"], "-1.6 9.8 -4.8": ["synergized"], "8.9 21.8 12.3": ["impudently"], "0.1 8.5 8.2": ["mootness"], "-1.3 -1.7 12.4": ["weel"], "-1.7 0.6 3.0": ["viol"], "5.7 11.5 41.4": ["gadwall"], "13.5 16.3 6.6": ["awesomest"], "-0.7 3.2 13.8": ["watermains"], "-11.9 3.5 4.9": ["spondylolisthesis"], "-4.6 5.3 7.9": ["subadviser"], "-2.8 4.1 5.9": ["securement"], "-1.4 4.8 4.2": ["cottaging"], "5.8 3.3 12.2": ["rimless"], "-3.7 8.2 -1.3": ["anglophile"], "0.6 -4.4 -1.7": ["prinicipal"], "6.0 3.4 9.0": ["brazed"], "2.9 13.3 13.1": ["fogy"], "4.2 3.8 9.5": ["raucousness"], "11.6 11.6 4.9": ["launderers"], "6.4 4.8 4.6": ["wonderfull"], "6.7 5.0 24.1": ["carbo"], "-11.7 8.3 4.0": ["lymphopenia"], "10.7 2.9 40.4": ["gravlax"], "4.1 9.0 14.4": ["lugar"], "5.6 6.0 12.0": ["floormat"], "3.2 -0.3 17.9": ["cornets"], "20.0 9.3 13.3": ["dizzily"], "-5.8 4.4 10.5": ["saidthat"], "11.6 1.6 4.3": ["ifo"], "11.4 8.4 12.2": ["rearmost"], "9.6 -1.3 12.1": ["ys"], "-0.2 5.3 13.1": ["chording"], "-5.0 2.8 7.3": ["nonparticipants"], "-0.3 14.7 4.3": ["disapointment"], "-1.3 0.4 6.4": ["lipoatrophy"], "2.0 13.2 4.3": ["panchnama"], "-4.8 9.5 1.0": ["depersonalization"], "13.7 9.1 16.9": ["kawaii"], "-0.4 12.8 7.1": ["insolation"], "9.0 2.2 7.5": ["patchworks"], "9.3 6.6 23.9": ["twines"], "18.3 6.9 1.9": ["conveyers"], "7.5 16.5 8.8": ["catcall"], "1.9 2.9 24.7": ["gelatos"], "-0.7 18.0 1.6": ["wherefrom"], "-1.2 6.3 0.5": ["whil"], "4.3 5.5 12.0": ["cusps"], "0.8 15.8 4.8": ["skippable"], "-1.4 -1.7 9.4": ["pmon"], "14.0 16.8 14.3": ["philistinism"], "15.2 6.6 20.2": ["crofter"], "4.8 6.1 5.0": ["regulative"], "4.3 9.3 13.4": ["khaps"], "-7.3 2.0 6.3": ["nonstudent"], "12.2 14.2 16.3": ["humbugs"], "17.7 12.5 10.2": ["hexed"], "12.4 3.0 15.1": ["fae"], "-4.5 9.8 12.5": ["icetime"], "22.3 7.0 6.6": ["coporate"], "14.2 3.2 15.0": ["purrfect"], "12.0 27.5 8.8": ["brutishness"], "3.1 0.1 1.0": ["unstitched"], "-3.5 21.3 1.5": ["vacillates"], "10.5 23.3 6.4": ["colludes"], "17.6 19.7 19.6": ["impales"], "1.1 6.7 3.2": ["overweights"], "5.3 14.2 6.8": ["conjoining"], "-2.1 3.8 9.3": ["subprojects"], "0.7 19.4 8.6": ["harrowingly"], "10.3 21.9 9.9": ["autarky"], "8.9 3.3 6.1": ["laundrette"], "7.4 0.9 28.7": ["smallgoods"], "5.0 11.1 8.5": ["dropsy"], "7.1 11.9 13.6": ["breeching"], "9.8 7.4 45.1": ["porbeagle"], "8.3 3.8 4.7": ["ultrasmall"], "2.8 25.3 18.4": ["minesweeping"], "4.0 7.1 13.6": ["percocet"], "-3.3 6.8 20.3": ["burgundies"], "3.5 9.9 20.4": ["mang"], "-0.8 13.0 4.7": ["unsubscribing"], "-1.4 -1.9 6.7": ["dati"], "1.9 6.5 9.1": ["distension"], "-6.5 0.7 8.0": ["representivity"], "1.7 10.2 1.0": ["gigabeat"], "10.7 -9.6 6.6": ["toda"], "10.5 11.3 7.9": ["volubly"], "-0.8 13.6 5.0": ["allocators"], "-0.8 15.7 12.1": ["hards"], "5.5 16.4 2.9": ["consistenly"], "-11.8 11.0 1.5": ["cannulation"], "3.5 9.6 2.6": ["podunk"], "4.5 11.4 5.1": ["esq"], "7.4 7.8 4.6": ["coud"], "9.2 4.1 17.4": ["midsections"], "15.8 8.1 6.1": ["frontrower"], "7.2 23.6 3.6": ["fitna"], "10.1 21.9 8.9": ["anthropocentric"], "6.2 4.9 21.2": ["nurserymen"], "8.4 17.6 13.2": ["monosyllables"], "10.2 -1.2 -0.3": ["ioko"], "-1.1 -7.6 8.6": ["postgrad"], "9.8 5.0 15.2": ["eet"], "11.6 9.5 10.8": ["ramada"], "3.8 4.4 12.8": ["equitization"], "17.9 19.8 18.0": ["rictus"], "11.4 -3.1 5.6": ["incudes"], "-1.2 9.5 13.5": ["unscientifically"], "-1.2 25.9 0.6": ["takfir"], "8.5 5.3 10.9": ["catadores"], "2.3 1.9 3.2": ["sprintcar"], "7.6 13.2 17.4": ["biddies"], "10.8 2.9 9.2": ["coaters"], "12.9 7.8 11.4": ["noooo"], "7.5 24.4 6.8": ["brethrens"], "7.2 3.5 6.1": ["flatrate"], "11.4 11.1 17.6": ["decorously"], "2.5 19.4 3.6": ["rangefinders"], "9.7 31.8 13.9": ["cavalryman"], "2.6 19.6 12.3": ["cocaleros"], "3.5 14.1 6.5": ["prodrugs"], "14.0 11.3 0.3": ["nanotechnologists"], "-1.2 5.7 6.9": ["petrolatum"], "7.9 2.1 27.9": ["gorditas"], "3.3 -0.0 4.2": ["vy"], "12.2 8.2 15.1": ["freakishness"], "-5.1 1.6 13.6": ["medyo"], "16.1 11.8 10.4": ["polysyllabic"], "0.4 10.3 -5.0": ["ofhis"], "2.6 16.8 5.9": ["inveigh"], "2.1 1.9 7.5": ["frameset"], "-0.6 17.6 5.5": ["believeth"], "13.4 29.6 14.4": ["untamable"], "9.4 -5.3 15.8": ["arrivederci"], "3.1 11.8 16.1": ["monazite"], "21.6 25.4 18.0": ["sandman"], "10.9 9.5 9.2": ["seediest"], "-2.2 -3.1 4.6": ["lodgements"], "8.9 11.0 10.2": ["ugg"], "16.3 6.3 11.4": ["subpanel"], "2.6 -0.3 13.9": ["thyroids"], "6.5 10.1 13.5": ["chemotaxis"], "-3.7 9.1 6.6": ["nanoribbons"], "16.2 17.1 6.1": ["goatherd"], "3.9 10.6 15.1": ["lebron"], "9.5 13.9 6.5": ["vodafone"], "-2.9 -2.2 -6.8": ["atomoxetine"], "2.5 24.4 1.4": ["tribalists"], "2.2 10.1 17.4": ["hefeweizen"], "28.3 7.3 6.6": ["geodesic"], "14.3 6.4 16.6": ["austerely"], "6.7 1.1 8.4": ["balder"], "6.9 0.2 2.6": ["survery"], "-2.5 5.7 16.4": ["chal"], "12.4 10.3 12.4": ["fluorescing"], "18.5 0.6 8.7": ["nieuwe"], "7.3 2.8 5.0": ["ultrasonics"], "10.1 -4.2 7.4": ["tenative"], "0.3 6.1 11.6": ["trivalent"], "-5.8 6.9 6.7": ["eribulin"], "-0.5 24.0 1.0": ["unsayable"], "-1.0 19.9 8.6": ["amateurishness"], "-0.3 6.3 0.7": ["subdivisional"], "-3.6 -6.6 -2.7": ["perfomed"], "-4.2 7.2 3.6": ["esophagitis"], "2.4 1.1 11.8": ["grandslam"], "2.0 0.3 5.5": ["curtainraiser"], "8.3 10.1 4.3": ["realer"], "9.0 31.4 14.0": ["leathernecks"], "1.2 2.8 14.9": ["crossties"], "4.1 12.0 30.8": ["hinds"], "1.9 11.1 5.7": ["embargoing"], "-0.3 4.2 1.8": ["upfit"], "1.7 -2.9 7.5": ["edwards"], "-2.0 18.7 18.3": ["influenzas"], "2.4 13.9 4.5": ["kayoed"], "8.7 15.1 8.0": ["dopest"], "9.1 8.0 8.0": ["dustmen"], "8.3 -1.2 9.9": ["tittered"], "21.7 11.0 28.8": ["maximus"], "8.0 5.8 5.2": ["initatives"], "4.6 17.2 5.0": ["benumbed"], "1.4 6.0 3.9": ["usenet"], "-0.7 11.7 18.5": ["jeremy"], "5.4 -2.4 -1.1": ["intitial"], "13.7 -1.9 6.2": ["swanned"], "-7.5 16.8 18.6": ["overwash"], "-2.0 14.6 11.1": ["generalizes"], "7.3 11.3 2.8": ["isothermal"], "7.4 19.3 -2.3": ["disseminator"], "9.1 7.0 20.1": ["henhouses"], "19.2 26.7 6.9": ["vaporise"], "7.3 4.6 24.2": ["lau"], "13.9 17.1 1.8": ["synergising"], "11.1 10.2 10.9": ["feck"], "13.6 17.2 13.2": ["escarpments"], "-6.8 -1.9 8.5": ["cornetist"], "-1.6 16.1 1.8": ["domestiques"], "19.4 -3.9 11.1": ["earings"], "-2.2 0.6 13.4": ["intertie"], "6.6 9.1 16.0": ["caudal"], "2.0 17.7 18.9": ["homeports"], "6.1 20.2 -2.5": ["countenancing"], "-1.8 4.4 3.2": ["swaption"], "4.9 8.9 34.5": ["kasha"], "13.7 9.9 13.6": ["punker"], "-4.0 14.2 -0.8": ["mediaperson"], "8.0 8.9 11.4": ["breeziness"], "-7.0 6.7 5.4": ["ort"], "-3.9 11.0 8.7": ["dutiable"], "5.0 3.8 8.5": ["arkansas"], "6.8 13.9 9.4": ["ecomony"], "-0.7 4.0 3.9": ["aclidinium"], "0.3 6.8 12.5": ["primogeniture"], "12.8 1.0 8.0": ["diy"], "-4.7 20.9 -0.5": ["plainclothesmen"], "-3.2 17.4 9.8": ["verbage"], "16.5 9.0 15.6": ["cowlick"], "7.1 3.1 7.8": ["argentina"], "2.8 9.6 21.0": ["jades"], "-9.1 10.7 2.1": ["cashers"], "16.0 -1.3 -1.8": ["muchneeded"], "16.4 4.8 17.8": ["brocaded"], "10.6 5.2 7.6": ["earls"], "4.3 6.7 21.8": ["menthols"], "3.2 -1.0 9.9": ["jacketing"], "4.6 -5.2 5.0": ["boul"], "-5.9 7.6 3.4": ["blepharospasm"], "-0.8 12.3 11.3": ["disparately"], "16.7 16.0 7.0": ["godhead"], "14.2 4.6 27.2": ["marbleized"], "2.5 13.1 5.0": ["funda"], "5.2 5.1 14.5": ["neh"], "-2.2 -0.9 5.1": ["timesharing"], "0.0 10.9 3.5": ["charismatically"], "9.7 -3.5 15.6": ["caplet"], "-4.1 0.1 -0.8": ["sequestrated"], "3.9 10.1 12.4": ["maternally"], "4.1 14.9 4.5": ["legation"], "5.3 7.6 5.3": ["sud"], "0.8 3.1 9.7": ["ionophores"], "12.7 13.9 20.5": ["translucence"], "13.4 7.7 8.2": ["combover", "binkies"], "-0.1 6.9 4.1": ["pardonable"], "-5.5 17.5 4.1": ["decisionmaker"], "5.8 9.9 14.1": ["newton"], "1.0 1.4 33.9": ["garbanzos"], "14.5 8.0 17.7": ["moppets"], "6.5 6.6 2.3": ["undertaxed"], "4.5 4.2 7.8": ["hyeon"], "8.3 -0.8 12.9": ["industryites"], "4.1 3.7 14.7": ["hie"], "-1.9 4.6 4.7": ["upconverting"], "15.9 17.6 10.4": ["oligarchical"], "4.2 13.0 10.1": ["disposer"], "3.9 2.4 9.2": ["submarined"], "-3.3 -4.2 14.1": ["phytase"], "6.6 20.1 2.4": ["cyberbully"], "-0.9 9.1 2.4": ["restrictively"], "-0.7 10.7 4.5": ["griots"], "11.6 11.8 6.5": ["doppler"], "22.9 12.9 22.2": ["thumbtack"], "12.9 15.8 22.1": ["dreadnought"], "-0.6 14.4 15.7": ["tyring"], "8.6 11.2 10.5": ["nowdays"], "7.7 16.7 3.9": ["deconstructive"], "7.4 1.0 11.1": ["boardsports"], "9.1 11.5 27.5": ["javelinas"], "0.2 16.4 8.6": ["triteness"], "10.3 2.6 14.1": ["fabbed"], "7.4 -0.4 9.7": ["daf"], "14.0 -1.3 -4.1": ["commercialises"], "-1.1 7.6 12.9": ["thumri"], "1.4 14.4 3.4": ["phosphine"], "0.0 7.3 7.6": ["apa"], "-7.4 5.0 10.4": ["arthrodesis"], "12.5 3.2 -9.1": ["ib"], "13.3 12.7 14.8": ["mau"], "4.8 2.6 -0.2": ["jah"], "22.4 20.9 20.9": ["soundlessly"], "5.5 5.1 -2.5": ["athe"], "18.9 29.7 16.0": ["unkillable"], "7.3 18.5 14.8": ["countervail"], "10.9 8.1 7.2": ["aesthetical"], "16.1 20.9 34.6": ["oxalis"], "6.3 4.7 9.3": ["molto"], "9.1 8.1 20.2": ["kiteboarder"], "-8.3 -3.8 5.4": ["playwrighting"], "14.6 14.9 24.8": ["snoot"], "-2.8 8.2 6.9": ["psychogenic"], "12.7 15.6 3.0": ["vulgarly"], "12.4 18.5 16.9": ["iciest"], "-4.0 11.1 2.2": ["responsable"], "6.9 14.5 -0.3": ["connoted"], "22.0 3.9 -2.7": ["rechristen"], "1.2 10.2 4.7": ["verklempt"], "2.2 1.0 16.5": ["dela"], "4.5 4.0 2.0": ["desulphurisation"], "-6.3 5.7 8.8": ["endoscopically"], "-7.0 20.6 -3.8": ["protectees"], "4.3 8.8 24.1": ["serviceberry"], "1.6 9.2 14.7": ["zekelogan"], "0.7 12.1 11.3": ["dallies"], "4.8 12.4 9.8": ["exabyte"], "3.0 -0.7 1.2": ["nanocrystalline"], "1.8 4.7 21.3": ["peices"], "7.2 25.7 15.2": ["unreturnable"], "7.2 5.3 5.8": ["mundo"], "16.4 24.0 17.9": ["baneful"], "14.3 12.0 9.4": ["doomsaying"], "-1.3 12.6 1.2": ["crashworthy"], "5.3 6.2 11.8": ["microchannel"], "4.7 11.4 14.5": ["salvor"], "1.3 8.7 12.4": ["nevi"], "6.8 6.2 13.2": ["freakouts"], "-2.0 25.7 -0.0": ["maltreat"], "1.3 2.1 -0.3": ["transesterification"], "2.3 11.9 2.8": ["accesible"], "-2.2 -1.9 1.5": ["ccs"], "6.0 18.7 5.3": ["humours"], "1.8 12.0 8.8": ["ironmen"], "4.0 0.2 10.4": ["ngo"], "12.0 4.3 11.7": ["nonagenarians"], "0.6 2.0 19.0": ["tika"], "14.2 2.4 7.9": ["drycleaner"], "14.9 11.3 -8.7": ["aquiring"], "-7.6 30.7 9.4": ["combatives"], "-4.8 17.2 -4.0": ["inspirer"], "10.6 13.5 34.7": ["bulrush"], "10.9 6.9 10.2": ["hoed"], "0.2 17.8 13.8": ["backpressure"], "4.1 4.7 15.0": ["dolce"], "15.2 25.0 13.1": ["anthropomorphizing"], "6.1 12.3 -1.6": ["atomistic"], "2.7 4.7 7.3": ["ofr"], "25.3 8.6 2.5": ["congloms"], "16.8 7.9 13.3": ["softdrink"], "8.4 16.4 12.2": ["yowls"], "1.5 -1.3 2.1": ["coachbuilder"], "9.3 4.4 12.3": ["whan"], "-0.3 20.1 4.8": ["falsifiable"], "15.2 11.3 14.5": ["breastplates"], "1.6 10.5 8.2": ["cowsheds"], "-0.7 5.6 12.7": ["pretournament"], "7.3 7.8 7.9": ["shitter"], "5.5 4.4 16.3": ["evensong"], "1.0 1.4 -0.9": ["submetering"], "3.7 16.4 11.6": ["gerrard"], "0.6 8.3 4.9": ["dysphoria"], "-0.5 8.1 9.2": ["mutiple"], "2.8 2.4 14.9": ["capful"], "24.8 5.1 24.0": ["gumboot"], "0.5 10.9 9.7": ["reshooting"], "-11.4 -1.8 -1.2": ["extern"], "9.0 9.5 19.7": ["digestif"], "-0.9 12.8 11.3": ["jaan"], "12.9 19.3 18.5": ["owlets"], "7.7 6.4 12.1": ["hypersexual"], "4.5 21.9 7.0": ["irresolution"], "4.4 13.2 9.7": ["astrologically"], "9.7 13.0 10.4": ["souled"], "10.1 3.6 14.2": ["freakier"], "6.5 3.6 12.9": ["brooklyn"], "5.1 6.2 13.8": ["lutz"], "13.1 20.4 10.1": ["easybeats"], "12.2 7.2 3.9": ["gullwing"], "5.8 10.9 10.1": ["trillionths"], "-9.5 6.7 6.1": ["quinolones"], "6.0 6.9 13.0": ["bighearted"], "-7.0 -1.0 22.7": ["fino"], "5.2 3.4 4.6": ["rems"], "0.4 17.6 6.5": ["soundfield"], "7.0 10.7 16.4": ["flagrante"], "4.6 14.3 4.1": ["incomings"], "-0.3 6.6 9.6": ["apni"], "14.2 6.9 15.4": ["terrestrially"], "10.4 6.8 10.5": ["twentyfold"], "3.7 5.1 7.8": ["lala"], "-3.8 9.3 7.3": ["emulsifying"], "11.1 -0.6 33.5": ["rotini"], "16.1 6.2 16.0": ["palletising"], "2.8 3.8 4.0": ["fallings"], "0.6 19.7 2.1": ["foreseeably"], "10.5 11.6 13.5": ["gardner"], "12.6 2.8 7.5": ["superproducer"], "7.9 17.9 4.4": ["scintillation"], "4.5 1.1 23.1": ["varities"], "14.1 22.6 11.9": ["precipices"], "-1.1 8.9 5.5": ["heptathletes"], "9.0 3.7 6.0": ["garmenting"], "3.1 10.5 11.9": ["productivities"], "5.7 3.0 7.6": ["cumulating"], "4.6 16.6 10.2": ["cringingly"], "5.7 7.3 11.2": ["amide"], "12.0 4.4 12.3": ["showin"], "5.5 9.8 11.6": ["timba"], "-0.8 5.3 -2.7": ["zileuton"], "9.5 14.7 8.6": ["tiremakers"], "-4.5 18.8 5.1": ["remobilized"], "6.4 11.4 7.8": ["userland"], "-1.8 13.4 6.6": ["subcomponent"], "0.8 13.0 15.5": ["unfavoured"], "6.4 13.6 -5.8": ["recommits"], "4.6 21.9 7.3": ["nutball"], "8.7 6.1 11.7": ["webapp"], "5.2 4.1 4.7": ["roomiest"], "12.2 20.1 11.9": ["rappels"], "9.7 -10.2 15.8": ["victorian"], "13.4 -4.5 14.4": ["uncap"], "-5.4 12.1 0.6": ["reachability"], "6.5 4.0 22.3": ["reintroductions"], "5.3 8.9 0.0": ["orate"], "17.1 12.5 12.4": ["jobsworths"], "-8.0 5.7 2.9": ["hematuria"], "2.1 3.9 0.2": ["binaural"], "7.0 16.6 6.8": ["spake"], "-7.0 2.5 5.1": ["uprates"], "5.8 4.7 10.2": ["itll"], "0.3 10.9 0.5": ["responsibile"], "-1.7 10.5 11.6": ["majimbo"], "16.7 7.6 4.1": ["trackballs"], "15.1 31.7 17.4": ["pillagers"], "7.4 17.0 30.7": ["woodies"], "10.7 9.7 6.2": ["gnashed"], "-5.7 8.5 6.1": ["lobectomy"], "5.2 6.7 6.6": ["preformatted"], "6.6 14.3 10.8": ["libertines"], "9.7 9.5 17.2": ["troth"], "3.4 2.1 7.1": ["doen"], "8.8 -1.2 15.7": ["floorball"], "7.3 1.6 8.2": ["bilingually"], "0.9 6.8 9.0": ["balun"], "-0.5 5.5 14.4": ["caulks"], "11.5 10.7 27.3": ["cordage"], "6.9 16.6 -0.8": ["enthroning"], "13.9 4.5 19.4": ["wakeboards"], "0.7 5.8 4.4": ["histopathological"], "6.1 12.2 4.5": ["superimposition"], "-2.6 13.8 7.3": ["tropism"], "6.5 -0.2 13.4": ["kwashiorkor"], "3.9 -2.4 1.5": ["incentivisation"], "8.4 8.2 29.4": ["brinjals"], "-5.1 0.8 4.3": ["cumulate"], "9.3 12.6 4.8": ["unstylish"], "29.2 -0.2 0.3": ["preopen"], "7.6 15.0 18.7": ["emma"], "2.5 20.1 0.4": ["communalise"], "-1.8 1.7 7.1": ["transmembrane"], "6.9 5.7 11.6": ["furan"], "2.0 14.4 27.9": ["julep"], "2.5 37.4 11.4": ["outfight"], "5.1 2.3 26.3": ["lima"], "-2.5 -0.1 8.2": ["scruffier"], "6.0 14.1 6.1": ["palpitation"], "1.7 6.5 7.4": ["anchorperson"], "6.6 14.6 11.7": ["mysteriousness"], "8.2 12.7 19.1": ["phyla"], "-1.0 29.5 8.1": ["revanchist"], "3.4 12.5 9.6": ["fluorophores"], "5.8 8.1 17.3": ["melissa"], "-4.1 15.2 10.5": ["parsha"], "3.9 12.3 23.8": ["goldenseal"], "4.5 11.5 5.7": ["agonises"], "4.1 6.5 14.7": ["salerooms"], "6.2 15.0 2.9": ["bodying"], "4.6 2.4 6.7": ["metrowide"], "13.4 12.8 1.8": ["unrealizable"], "-1.9 8.6 14.5": ["shakuhachi"], "13.4 5.3 10.1": ["irradiator"], "-1.1 1.4 5.5": ["backsheet"], "12.6 18.7 7.6": ["transfix"], "3.0 8.7 14.5": ["flulike"], "9.3 28.9 16.8": ["ravish"], "7.5 13.1 13.3": ["earthed"], "6.6 0.8 10.4": ["pone"], "10.0 1.9 2.0": ["multilanguage"], "16.7 4.8 29.2": ["trivet"], "9.9 4.1 5.0": ["trac"], "10.6 13.1 2.3": ["destine"], "0.2 15.4 2.8": ["unenjoyable"], "0.1 -0.9 7.4": ["bih"], "15.9 14.2 26.6": ["huck"], "9.1 6.8 5.1": ["durch"], "14.1 14.6 8.4": ["slews"], "12.7 7.0 14.7": ["cirrus"], "-1.9 0.7 3.6": ["vitae"], "11.6 5.6 19.2": ["horsed"], "4.6 -1.6 4.7": ["avaialble"], "12.2 7.1 5.6": ["ponzi"], "-5.9 11.9 5.6": ["outraise"], "8.0 16.4 0.9": ["arround"], "-0.8 5.3 15.6": ["gaye"], "9.1 6.4 0.4": ["brawnier"], "8.7 0.2 15.3": ["penn"], "7.3 13.0 5.5": ["afterwords"], "17.1 14.5 21.5": ["jta"], "-2.7 4.5 16.5": ["sparsity"], "8.8 13.6 5.3": ["wakening"], "0.2 6.6 -2.7": ["podcar"], "5.7 21.3 12.6": ["bunkmates"], "7.5 25.1 -0.5": ["weaponizing"], "8.0 31.2 5.6": ["narcoterrorists"], "-6.4 21.2 8.4": ["epistemic"], "0.7 8.9 12.0": ["snootiness"], "-0.6 1.8 8.3": ["meetin"], "14.1 10.0 1.7": ["thatit"], "5.3 -0.6 10.7": ["ranitidine"], "-1.1 3.5 3.6": ["pericardial"], "9.3 7.2 23.0": ["papad"], "1.5 2.4 -4.3": ["rivastigmine"], "2.5 10.5 14.5": ["fossilization"], "10.1 13.8 6.6": ["dictat"], "5.5 5.6 25.3": ["slipways"], "-0.8 8.0 5.0": ["possesions"], "-3.9 8.0 5.8": ["webseries"], "11.9 6.1 22.9": ["mukluks"], "10.7 6.3 25.6": ["schmear"], "4.8 1.8 10.5": ["leones"], "19.3 9.3 21.5": ["smores"], "5.3 12.7 3.0": ["acerbically"], "0.9 6.8 -0.3": ["pickpocketed"], "15.9 8.9 43.9": ["limpets"], "-3.2 -3.3 4.9": ["laminectomy"], "19.8 3.9 13.2": ["moos"], "5.4 5.6 28.4": ["madeleines"], "14.6 13.0 17.9": ["gropers"], "4.4 9.9 3.1": ["breakins"], "5.7 1.9 5.6": ["recomend"], "0.2 5.8 8.9": ["bloodmobiles"], "7.5 2.7 13.1": ["wx"], "-1.6 12.0 7.2": ["philologist"], "-4.1 9.0 0.1": ["remunerating"], "11.9 21.7 12.6": ["despoliation"], "10.4 16.8 11.3": ["femaleness"], "20.2 16.1 12.1": ["multibillionaires"], "13.5 37.5 11.6": ["minimap"], "16.0 9.8 8.7": ["supergrid"], "5.5 2.0 4.3": ["redlined"], "8.0 11.4 6.9": ["carrie"], "-5.4 9.6 3.8": ["abbess"], "5.6 7.2 12.4": ["voyaged"], "8.4 4.8 13.5": ["toilette"], "11.8 10.6 18.9": ["sheila"], "14.9 16.7 29.1": ["popover"], "-5.5 15.8 8.0": ["gimmies"], "11.5 -4.0 -0.9": ["opto"], "2.3 13.0 3.1": ["stupefyingly", "leagal"], "12.4 16.8 13.5": ["onomatopoeic"], "1.0 11.0 7.7": ["afghani"], "5.7 -1.4 15.6": ["fina"], "4.2 5.9 5.0": ["rl"], "4.4 9.8 6.6": ["moneychanger"], "6.5 3.9 20.4": ["amniotic"], "3.5 1.1 1.4": ["dematerialisation"], "-0.7 6.7 7.4": ["picocuries"], "17.9 6.3 28.0": ["flambe"], "1.7 1.0 5.6": ["resorbable"], "-2.3 8.2 -0.7": ["cyberbullied"], "-1.0 3.5 9.5": ["atv"], "6.6 5.1 1.3": ["vouchsafe"], "-2.4 11.5 -2.8": ["oppositon"], "2.7 1.0 2.9": ["hypersexuality"], "9.0 5.2 25.4": ["unglazed"], "2.3 6.3 7.6": ["recordkeeper"], "0.3 13.5 36.0": ["muscadines"], "12.0 10.9 10.8": ["drumhead"], "8.0 14.3 8.5": ["straightedge"], "-2.9 13.6 11.0": ["chahiye"], "7.2 11.8 14.8": ["kenny"], "-1.0 8.6 9.7": ["strokemaker"], "-5.9 10.8 2.5": ["commentor"], "8.5 15.1 5.8": ["aerobridge"], "10.4 13.2 23.8": ["crisping"], "10.7 14.3 7.7": ["mistype"], "14.0 16.2 18.7": ["lollygag"], "13.8 9.4 14.8": ["mook"], "9.9 14.6 9.4": ["defenestration"], "9.7 15.5 7.7": ["funnily"], "0.3 14.3 1.6": ["consitution"], "10.2 18.0 5.1": ["dismissible"], "4.8 12.9 13.2": ["aestheticism"], "18.6 -0.4 17.5": ["cheesey"], "-2.9 9.0 5.6": ["wasta"], "13.3 14.9 27.9": ["hollyhock"], "-6.9 9.8 51.6": ["bottomfish"], "26.2 12.5 18.8": ["birdman"], "2.7 0.2 8.1": ["chainstays"], "5.0 22.9 8.4": ["egocentricity"], "8.4 2.1 8.0": ["megaresorts"], "0.8 -8.3 13.0": ["fractionator"], "14.8 10.6 16.7": ["undie"], "6.3 5.5 4.4": ["gyratory"], "-0.9 13.0 8.9": ["emigrates"], "4.0 12.2 18.6": ["photosynthesize"], "10.7 11.9 18.7": ["pash"], "-4.2 5.0 14.6": ["duathlons"], "5.4 0.7 12.4": ["sportcoat"], "7.6 8.5 4.4": ["photometer"], "6.6 5.4 10.7": ["guiderail"], "2.9 19.8 3.4": ["redeemers"], "-5.4 39.6 14.5": ["debuff"], "12.2 2.4 16.0": ["pou"], "0.4 6.1 11.8": ["iyon"], "-1.4 11.1 6.5": ["organogram"], "6.1 4.6 10.4": ["aspx"], "8.4 4.7 23.5": ["mits"], "9.6 1.3 8.7": ["whitebox"], "1.4 8.8 13.5": ["aerobraking"], "4.2 5.6 9.5": ["freeskier"], "6.8 11.6 1.3": ["inturn"], "-0.9 6.9 3.6": ["logjammed"], "1.8 12.2 1.2": ["wld"], "9.3 10.9 6.8": ["sarkari"], "-2.9 8.1 24.4": ["enterococcus"], "9.2 -10.2 6.2": ["fasttrack"], "16.4 5.1 13.7": ["doona"], "19.6 4.0 13.3": ["roustabouts"], "11.3 11.1 7.3": ["naughtily"], "0.4 19.3 14.9": ["recursion"], "-0.5 4.6 3.7": ["aspirating"], "-2.0 1.7 11.2": ["condotel"], "6.0 0.4 14.5": ["craftspersons"], "0.3 10.9 8.0": ["coital"], "-2.3 10.0 0.8": ["nonregion"], "15.6 11.5 15.3": ["gangbang"], "6.8 1.8 0.9": ["diese"], "6.1 -6.5 9.1": ["chiropody"], "5.1 13.9 12.2": ["reflexivity"], "6.9 10.4 14.1": ["badinage"], "9.4 2.8 26.1": ["noshes"], "13.9 11.4 31.9": ["shrike"], "14.3 11.2 36.3": ["stickleback"], "8.9 16.1 7.4": ["videocam"], "8.2 4.8 12.9": ["ooops"], "6.9 2.0 14.2": ["hotrods"], "11.2 3.4 12.1": ["footware"], "5.7 18.4 5.6": ["dunderheaded"], "13.1 -0.6 7.2": ["plastinated"], "13.4 3.7 10.0": ["ultrarich"], "16.0 13.5 19.6": ["tatami"], "3.7 24.1 1.4": ["jingoist"], "18.4 22.1 10.0": ["simulacra"], "8.8 2.6 15.2": ["nisi"], "3.2 8.1 8.6": ["multiemployer"], "16.0 17.3 7.0": ["hypnotizes"], "-0.6 6.6 8.1": ["boes"], "7.6 11.1 3.3": ["besmirches"], "10.9 3.2 11.0": ["growed"], "-0.7 10.5 20.8": ["heiau"], "17.8 8.1 11.7": ["undergound"], "8.9 4.8 17.4": ["shirtsleeve"], "6.8 14.9 23.5": ["hyssop"], "2.9 8.0 9.5": ["oba"], "1.4 -2.9 0.9": ["neighborsgo"], "-0.7 11.2 6.3": ["photometry"], "8.3 0.5 16.4": ["tailcoat"], "14.5 11.5 12.4": ["zillionth"], "2.0 10.4 12.2": ["biogeochemical"], "24.1 12.7 28.2": ["inchworm"], "1.0 11.7 8.7": ["oppinion"], "-0.3 10.5 -2.4": ["postulations"], "3.5 -0.5 11.3": ["mlb"], "8.1 19.2 10.3": ["allcomers"], "-3.8 8.2 -3.8": ["ablations"], "10.9 6.8 11.5": ["lentivirus"], "12.5 12.2 14.7": ["bobo"], "7.2 3.3 5.5": ["abercrombie"], "-3.4 -10.1 8.7": ["musicale"], "-3.4 16.1 -3.5": ["achive"], "7.2 12.8 11.5": ["drogba"], "3.3 23.8 9.8": ["backmen"], "7.2 19.0 4.7": ["antifascists"], "-3.5 1.9 6.9": ["visionapp"], "3.7 31.3 6.2": ["terrorization"], "13.9 16.1 12.2": ["pacman"], "8.0 12.1 11.1": ["dipoles"], "3.0 3.3 15.9": ["wats"], "3.9 4.7 11.7": ["aug"], "2.2 5.1 5.9": ["bewteen"], "14.4 13.3 6.9": ["fractionating"], "9.3 -3.6 5.7": ["giftcard"], "7.2 12.6 7.8": ["risibly"], "-1.7 1.2 7.6": ["mol"], "4.1 4.0 3.7": ["ultrashort"], "15.1 5.5 12.9": ["botoxed"], "-3.2 3.9 -1.8": ["dipyridamole"], "0.0 15.7 5.3": ["freind"], "0.4 8.2 11.3": ["warpage"], "15.1 8.5 11.0": ["multipack"], "1.0 8.3 18.6": ["ecotourists"], "14.3 12.9 16.8": ["hoser"], "12.3 12.5 36.8": ["tule"], "-4.1 10.6 3.9": ["captainship"], "6.4 9.6 0.1": ["gushingly"], "3.4 7.8 3.3": ["perecent"], "18.2 2.9 4.5": ["afficionado"], "16.6 9.2 23.2": ["satyrs"], "8.2 7.7 5.2": ["defict"], "1.0 6.5 4.7": ["contemporized"], "12.5 -0.2 3.8": ["smartening"], "-0.6 13.2 4.5": ["prosody"], "-5.3 7.6 5.9": ["reconnections"], "25.4 22.2 22.9": ["eyeless"], "10.0 12.0 13.3": ["dynein"], "3.8 8.5 14.1": ["flyaways"], "17.7 8.6 17.1": ["trencher"], "6.7 14.7 15.0": ["belaying"], "0.6 12.7 10.0": ["philosophized"], "4.1 5.4 15.8": ["makgeolli"], "4.8 8.2 12.2": ["interdicts"], "2.7 5.9 20.9": ["zi"], "2.8 11.8 10.3": ["overserved"], "3.4 2.0 15.4": ["wuh"], "12.2 2.8 13.4": ["schnauzers"], "0.9 12.6 14.2": ["outerbelt"], "1.7 13.6 13.1": ["unowned"], "-2.5 3.6 22.4": ["exactas"], "-10.3 1.0 -2.3": ["testbenches"], "15.6 16.3 24.2": ["jackdaws"], "6.8 7.6 10.7": ["kk"], "16.9 9.4 22.5": ["mammaries"], "1.4 19.9 12.7": ["psychologies"], "11.5 0.3 14.0": ["lurex"], "-5.3 13.4 7.4": ["outpunched"], "19.8 12.5 14.2": ["fricken"], "14.5 3.8 11.5": ["eyepopping"], "6.0 7.0 10.6": ["centromere"], "8.0 27.8 7.8": ["supremacism"], "15.9 7.3 16.5": ["chaises"], "8.0 24.6 3.9": ["multirole"], "4.0 12.2 14.4": ["celtics"], "10.9 3.7 10.0": ["pam"], "1.0 1.7 13.9": ["poplin"], "0.4 2.2 5.6": ["lation"], "6.4 31.2 10.3": ["subjugates"], "-13.0 3.0 1.5": ["reprioritized"], "1.0 -0.0 6.0": ["oss"], "-8.2 13.3 9.1": ["suspiciousness"], "9.3 5.4 7.2": ["eclectically"], "16.8 10.8 13.1": ["phenomenom"], "11.5 -0.9 8.7": ["draper"], "3.3 12.2 -2.9": ["concretized"], "1.1 4.2 10.2": ["tage"], "13.8 9.6 13.6": ["froths"], "12.0 -9.4 -2.1": ["mllion"], "20.4 11.0 53.1": ["whelk"], "5.8 17.0 16.1": ["breakables"], "7.0 1.4 16.7": ["nerdcore"], "4.6 0.9 15.7": ["trackways"], "7.2 15.3 -0.5": ["gridding"], "7.1 12.6 10.8": ["fictitiously"], "-0.4 2.4 16.1": ["maraming"], "4.1 14.1 9.5": ["loth"], "8.5 12.7 13.8": ["confluences"], "14.7 14.7 14.5": ["spreadeagled"], "6.4 20.3 10.9": ["oldschool"], "1.0 5.2 1.3": ["mediastinal"], "0.6 9.5 7.0": ["encryptions"], "2.1 12.6 10.8": ["bhabhi"], "2.5 14.6 -1.5": ["forswearing"], "6.2 8.2 12.9": ["loosener"], "6.4 3.3 3.5": ["indesign"], "14.3 7.4 8.8": ["crushable"], "15.4 4.7 8.9": ["rattletrap"], "-5.1 14.7 -5.9": ["isnot"], "20.5 6.8 17.3": ["sheering"], "-1.6 5.9 5.3": ["preservations"], "9.9 -5.8 11.7": ["hairband"], "17.3 18.7 14.5": ["eyrie"], "16.4 10.1 12.4": ["grrr"], "-5.4 22.4 4.3": ["intercessor"], "4.3 10.7 4.5": ["porphyrin"], "7.0 7.8 19.1": ["colin"], "-3.4 6.2 8.2": ["papillary"], "-6.9 1.1 5.6": ["cyberschool"], "15.0 7.7 11.1": ["halfwits"], "-0.5 7.9 12.1": ["presenilin"], "9.8 3.3 18.0": ["pennycress"], "5.5 -2.7 2.8": ["spacy"], "11.1 7.4 35.3": ["foie"], "5.8 14.8 3.0": ["cryptographically"], "-2.5 11.8 3.5": ["dyskinesias"], "7.7 1.3 3.4": ["unremitted"], "2.6 11.5 3.6": ["stylize"], "6.3 8.6 39.3": ["steelies"], "-2.5 15.5 4.5": ["supressed"], "10.7 0.1 9.7": ["aunque"], "1.3 2.1 9.4": ["nanolithography"], "-1.9 6.0 8.6": ["timpanist"], "1.3 12.8 0.2": ["ignitable"], "7.4 -1.0 5.1": ["stor"], "5.0 11.9 10.7": ["feild"], "12.6 13.8 19.3": ["facebuster"], "0.9 17.9 7.5": ["profaned"], "3.9 7.2 17.0": ["hsiang"], "5.4 17.4 13.1": ["straphanger"], "6.0 21.4 13.3": ["afterworld"], "6.0 12.2 10.6": ["monkish"], "16.3 3.4 12.9": ["aig"], "7.5 14.8 7.5": ["retardants"], "13.2 7.4 13.2": ["doncha"], "7.6 10.1 31.9": ["burgoo"], "7.8 10.6 2.7": ["externalised"], "5.1 16.0 5.8": ["supercells"], "3.9 18.1 14.5": ["skiddy"], "1.2 7.4 19.1": ["bodyboarder"], "8.5 12.8 19.2": ["tinnies"], "10.8 14.0 -0.1": ["flawlessness"], "3.1 15.9 9.7": ["geocacher"], "-6.7 6.2 4.4": ["ramelteon"], "0.2 15.5 0.5": ["fbi"], "0.3 7.9 4.6": ["stratifying"], "8.5 8.3 20.3": ["matzos"], "0.6 0.4 5.1": ["microentrepreneurs"], "-2.0 18.9 9.6": ["patronization"], "10.5 3.5 7.4": ["cokers"], "-4.6 1.1 -0.8": ["galantamine"], "5.5 1.4 20.1": ["prizepool"], "5.5 12.3 6.3": ["consecrates"], "3.5 7.0 11.7": ["tressed"], "19.4 6.9 11.1": ["sightly"], "-0.1 3.3 8.4": ["alanine"], "13.1 14.4 14.5": ["picturesquely"], "1.7 6.5 23.2": ["lightering"], "-1.1 20.8 2.4": ["wrenchingly"], "2.9 5.0 12.8": ["trashiest"], "18.4 21.3 4.8": ["tinpot"], "-1.4 17.7 2.6": ["delt"], "8.6 3.0 28.8": ["greaseless"], "8.9 6.0 7.3": ["entwines"], "0.9 14.3 -1.2": ["stike"], "5.2 -2.8 11.5": ["minn"], "2.2 6.8 24.8": ["channa"], "6.2 16.3 1.0": ["gnostic"], "9.9 24.3 36.1": ["salvinia"], "0.3 -1.8 3.0": ["duing"], "1.2 13.5 8.9": ["reformasi"], "4.2 6.0 11.2": ["bindaas"], "-3.8 7.0 6.8": ["zonisamide"], "3.1 7.3 2.8": ["crystallographic"], "-3.2 0.8 3.7": ["foundress"], "12.4 3.5 12.1": ["nhl", "highschooler"], "1.9 12.8 7.9": ["goaltend"], "10.5 1.4 4.5": ["percnet"], "1.9 3.7 10.4": ["ibogaine"], "2.9 0.4 3.7": ["thermochemical"], "8.0 9.1 21.8": ["caw"], "6.6 5.9 10.1": ["spackling"], "14.7 16.7 11.6": ["colorize"], "-2.7 -3.4 11.0": ["sharemilkers"], "14.5 14.7 27.4": ["cassowary"], "6.1 11.8 13.5": ["makeout"], "5.7 21.8 6.6": ["unclimbed"], "13.5 12.4 -2.2": ["rebadging"], "17.8 11.1 11.6": ["smeary"], "0.5 9.0 48.5": ["groundfishing"], "3.7 8.8 13.7": ["ileum"], "3.1 13.7 11.3": ["undevelopable"], "-3.9 2.6 7.0": ["instating"], "-1.2 14.4 25.3": ["bermuda"], "9.9 1.7 18.7": ["ollies"], "3.5 15.9 11.2": ["tresspassing"], "21.0 16.2 10.4": ["spotlit"], "-4.3 4.6 3.6": ["acheiving"], "-2.4 7.7 1.2": ["sermonising"], "5.2 -8.9 7.0": ["allo"], "14.0 1.9 6.0": ["baptistery"], "11.0 5.5 5.6": ["bargepole"], "5.6 18.0 14.0": ["bushranger"], "11.1 9.7 21.9": ["potholder"], "18.0 18.8 18.9": ["wolfman"], "22.9 9.8 8.4": ["squillions"], "9.8 12.8 8.7": ["mitochondrion"], "1.9 3.2 21.3": ["pomace"], "3.3 6.0 9.0": ["pseudocyesis"], "0.3 3.9 7.5": ["steriod"], "8.8 -1.2 8.0": ["screenprinting"], "-6.4 10.9 15.6": ["macronutrient", "abigail"], "7.6 0.7 12.6": ["playsuit"], "8.5 11.4 8.3": ["bummers"], "5.2 4.8 5.8": ["halaal"], "7.1 13.0 12.0": ["tremblor"], "-4.8 -2.0 12.4": ["vanpooling"], "-0.7 3.1 21.8": ["malay"], "0.3 3.3 11.2": ["maxillary"], "11.9 -0.2 -1.1": ["programm"], "13.9 1.9 11.3": ["coiffured"], "-1.8 13.0 1.5": ["siddur"], "-11.2 12.0 4.8": ["teshuvah"], "3.2 20.8 11.2": ["pelf"], "4.6 10.3 50.7": ["seatrout"], "14.1 16.1 5.9": ["soubriquet"], "10.7 0.1 35.0": ["manchego"], "-0.4 1.8 4.8": ["cermony"], "6.3 1.7 7.7": ["automobilia"], "-0.4 -4.0 0.3": ["bootcamps"], "-3.5 16.0 9.4": ["percenter"], "11.5 19.2 17.5": ["firehoses"], "1.7 7.1 12.1": ["trebly"], "16.4 3.8 3.0": ["lapdancer"], "13.1 14.1 10.4": ["aurorae"], "1.3 7.1 -1.3": ["dissociating"], "16.7 9.9 14.8": ["circumnavigates"], "3.2 5.6 10.7": ["rollcage"], "-4.0 4.2 1.2": ["optionee"], "-6.4 2.4 0.9": ["playlet"], "11.6 14.6 15.9": ["thieve"], "2.3 5.9 2.3": ["isotonic"], "-2.4 5.8 6.4": ["pinout"], "5.0 15.3 1.2": ["ignorable"], "17.5 5.0 13.4": ["gamboling"], "3.7 9.8 8.6": ["dolorous"], "0.9 21.1 -0.3": ["freethinker"], "-2.4 6.7 24.1": ["tumeric"], "10.2 9.3 9.8": ["clasts"], "-9.2 2.6 19.3": ["robustas"], "0.4 9.3 5.9": ["acclimates"], "2.8 3.2 13.1": ["concealers"], "22.2 11.2 2.2": ["resuscitates"], "7.2 20.7 8.1": ["oppressiveness"], "-5.5 5.7 -0.9": ["responsiblities"], "18.7 23.3 20.1": ["spyglass"], "-3.2 3.8 4.2": ["arthrogram"], "15.5 6.9 19.2": ["tokyo"], "10.0 7.6 10.3": ["glaciology"], "9.1 23.0 10.3": ["leashing"], "16.5 16.0 24.7": ["briar"], "-3.5 5.7 6.0": ["gradebook"], "5.6 14.0 13.7": ["struct"], "-10.9 19.5 2.9": ["aggravator"], "16.4 9.9 10.2": ["laded"], "5.6 -2.2 11.2": ["pedi"], "5.7 10.0 14.9": ["bankbook"], "6.9 8.5 8.4": ["cruisy"], "5.6 30.8 22.6": ["bagworms"], "16.0 12.4 16.8": ["collier"], "2.8 -0.6 7.3": ["brouhahas"], "7.1 16.0 10.7": ["streptococci"], "14.5 22.2 11.3": ["evilly"], "-10.5 3.7 1.1": ["leve"], "12.3 13.2 16.8": ["boodle"], "15.2 4.6 9.8": ["slaked"], "7.5 19.7 6.5": ["hillarious"], "-7.3 2.9 4.1": ["presentencing"], "4.2 13.0 18.2": ["kneebar"], "25.6 10.6 14.2": ["pentagons"], "7.2 14.1 -1.1": ["theat"], "3.1 1.2 2.9": ["tauter"], "2.2 1.6 8.9": ["thailand"], "33.3 26.0 13.2": ["blockheads"], "3.4 -3.5 6.5": ["ihn"], "10.0 1.8 6.7": ["woong"], "11.4 14.0 5.9": ["hushes"], "-3.9 -3.3 19.0": ["seedstock"], "3.6 5.9 8.5": ["nonplused"], "5.7 0.4 14.0": ["bor"], "10.9 3.8 3.4": ["matic"], "0.8 29.5 12.5": ["pararescuemen"], "-1.8 16.6 8.2": ["shelterless"], "12.5 18.7 17.9": ["asians"], "6.2 6.0 3.2": ["refurnish"], "13.0 1.2 21.1": ["jing"], "-4.2 7.3 4.3": ["scripters"], "11.2 10.0 10.9": ["afarensis"], "11.0 13.1 19.5": ["unset"], "3.5 -1.4 0.3": ["representive"], "7.2 7.6 16.2": ["doug"], "1.7 9.0 8.5": ["gateman"], "-1.9 5.2 19.2": ["skeletonized"], "4.4 23.5 15.0": ["moveset"], "-3.6 9.9 7.5": ["taal"], "-1.7 17.2 6.0": ["interparty"], "10.2 6.3 14.4": ["kibitz"], "1.2 7.9 7.8": ["tawdriness"], "5.0 10.6 15.1": ["arak"], "8.3 13.2 0.7": ["vatican"], "-1.6 2.5 15.5": ["overbuy"], "0.2 2.2 10.9": ["polytrack"], "6.8 8.0 6.8": ["reid"], "10.2 14.5 4.3": ["posturings"], "8.9 13.8 -4.6": ["outted"], "-1.7 15.2 15.6": ["misfields"], "-5.4 8.0 4.7": ["nelfinavir"], "-8.3 0.5 5.9": ["photoresists"], "-9.6 7.1 10.1": ["swara"], "20.8 10.7 0.3": ["acquisiton"], "10.1 7.5 8.7": ["nailer"], "15.0 3.5 37.1": ["bap"], "-5.1 10.2 3.0": ["upconverted"], "-2.9 2.8 5.6": ["bronchopneumonia"], "-0.5 12.2 8.5": ["emesis"], "7.8 18.2 8.4": ["thousandfold"], "4.4 7.1 17.7": ["pultrusion"], "0.2 12.2 11.3": ["plp"], "5.7 14.4 -0.9": ["voiceprint"], "-2.7 4.3 8.7": ["chattiness"], "6.8 4.7 17.3": ["chainring"], "-1.7 3.9 2.7": ["engraft"], "-1.9 4.3 -1.6": ["telithromycin"], "17.6 -1.3 22.5": ["poufs"], "14.6 1.5 13.0": ["beijing"], "1.3 4.1 11.6": ["magmas"], "2.0 6.1 5.7": ["iontophoresis"], "6.3 12.6 6.4": ["waterpower"], "-6.2 4.9 2.8": ["reinterview"], "9.8 11.0 13.5": ["acrostic"], "2.2 1.8 8.6": ["duirng"], "1.1 -5.7 4.5": ["injectibles"], "13.2 11.5 11.2": ["athwart"], "16.0 13.2 10.3": ["summersault", "toeholds"], "10.0 12.8 6.8": ["threatend"], "16.5 8.9 25.1": ["platypuses"], "6.4 20.6 5.9": ["supression"], "4.1 17.1 11.4": ["wuxia"], "18.1 8.0 16.9": ["unattractively"], "-3.7 10.9 6.9": ["serologic"], "1.1 10.6 13.5": ["roughie"], "9.2 2.5 32.0": ["pakora"], "5.4 16.8 10.0": ["uncomplainingly"], "8.7 4.6 11.9": ["herbalism"], "1.6 11.2 11.6": ["shaq"], "6.7 15.2 1.8": ["aggrandizing"], "-12.7 19.9 8.1": ["premeditate"], "-7.0 9.7 -1.1": ["etoricoxib"], "-0.4 2.0 6.1": ["adsorbents"], "2.5 1.3 8.2": ["ral"], "20.4 14.0 20.7": ["climbable"], "12.5 6.8 14.6": ["ascots"], "15.8 19.4 17.5": ["infantilizing"], "14.1 13.4 8.9": ["cmon"], "3.2 21.8 9.6": ["moonless"], "19.4 6.4 6.7": ["rollable"], "-3.5 13.1 13.5": ["quippy"], "19.5 4.0 14.9": ["fingerless"], "-0.9 3.8 6.1": ["pafuramidine"], "7.3 3.9 -4.8": ["oficial"], "13.0 12.4 14.6": ["pullin"], "9.0 8.7 11.0": ["fleshpots"], "4.7 10.3 15.2": ["taxol"], "6.3 7.6 7.2": ["lovelife"], "0.9 3.9 18.8": ["powerpc"], "-2.8 3.2 13.1": ["offtakes"], "3.4 16.3 10.7": ["historicism"], "20.9 9.8 44.0": ["fishies"], "10.9 10.7 1.9": ["telegraphy"], "18.3 5.2 5.8": ["citi"], "6.5 1.2 11.2": ["prothesis"], "3.7 16.5 5.6": ["secularly"], "14.3 9.9 11.2": ["abloom"], "1.9 5.5 8.0": ["regularseason"], "17.6 6.6 19.8": ["gnashers"], "3.9 4.4 10.9": ["multis"], "-3.0 5.3 10.9": ["mukim"], "-1.9 25.3 1.7": ["necesary"], "-1.8 1.9 9.8": ["mushaira"], "3.5 3.8 19.7": ["hardscaping"], "10.4 23.5 14.4": ["lectins"], "5.2 3.7 -0.4": ["laga"], "20.1 7.6 7.8": ["holics"], "8.4 6.9 20.8": ["rudbeckia"], "5.4 7.3 6.5": ["dealin"], "3.7 6.0 2.7": ["masstige"], "0.8 10.2 7.2": ["clearcoat"], "3.5 -2.8 15.6": ["ato"], "2.7 16.9 13.5": ["wayfarer"], "-9.7 8.4 3.3": ["decommit"], "7.9 19.7 7.8": ["undiscerning"], "13.9 8.1 11.1": ["circumferences"], "4.7 20.9 6.9": ["vizier"], "-0.9 3.9 0.5": ["decelerations"], "4.3 11.5 6.4": ["unaggressive"], "0.5 9.3 18.3": ["anaplasmosis"], "17.6 18.8 36.0": ["grackle"], "16.0 3.1 11.7": ["coiffures"], "-0.1 3.7 13.5": ["hardrock"], "-3.9 5.2 2.3": ["gurantee"], "5.9 -1.7 4.7": ["nlyte"], "8.8 18.6 7.6": ["magnetars"], "3.0 -3.2 2.6": ["fumblings"], "10.9 17.2 9.1": ["logarithms"], "15.7 2.3 13.1": ["diddled"], "6.6 15.3 6.1": ["rebuilders"], "13.1 -1.1 7.4": ["fim"], "-3.8 1.4 6.1": ["activies", "cryptorchidism"], "-4.8 2.1 4.1": ["microsurgical"], "10.6 2.2 17.0": ["carters"], "15.4 16.1 19.2": ["drainer"], "3.7 8.3 5.8": ["planograms"], "-6.8 5.2 1.0": ["updation"], "4.4 10.8 15.6": ["impasto"], "-1.4 31.8 7.6": ["cowardliness"], "8.6 3.2 8.3": ["undercroft"], "8.2 9.9 8.1": ["edgers"], "-5.4 7.3 4.2": ["depositaries"], "4.8 7.2 -0.4": ["explusion"], "-3.9 7.3 -0.2": ["apraxia"], "2.4 -3.9 1.0": ["glucometers"], "-6.0 1.7 -6.2": ["thrombectomy"], "0.7 13.0 15.9": ["clockspeed"], "1.1 3.3 3.9": ["angolan"], "5.6 3.9 19.3": ["taxon"], "-1.3 15.7 -2.5": ["gainsaid"], "0.6 18.3 5.2": ["lifework"], "-0.3 7.6 -5.1": ["totake"], "21.1 2.5 33.5": ["gentoo"], "3.3 9.5 6.5": ["hypermilers"], "15.3 19.4 21.2": ["anthills"], "17.9 4.3 4.2": ["tieups"], "14.1 15.0 7.3": ["coliseums"], "1.1 29.4 -4.1": ["attrocities"], "3.7 14.2 0.3": ["entrepreneurially"], "1.5 19.1 11.1": ["depersonalized"], "10.3 13.6 31.7": ["cygnet"], "-0.1 -3.3 7.9": ["readmitting"], "5.3 6.8 10.2": ["pompeyrug"], "4.1 25.3 9.7": ["paki"], "-4.4 1.5 6.3": ["neuroradiologist"], "0.9 22.5 8.0": ["relativists"], "4.3 16.3 13.4": ["triers"], "-1.7 12.9 13.6": ["overslid"], "9.6 7.7 9.9": ["unpadded"], "-5.6 0.6 3.9": ["solemnise"], "5.1 14.0 5.2": ["intresting"], "5.5 -5.1 -1.8": ["kbd"], "-3.9 9.5 6.6": ["homerism"], "9.0 7.2 18.8": ["kneads"], "-1.4 9.1 3.0": ["superceding"], "9.8 12.3 0.5": ["suspicous"], "4.6 21.6 7.8": ["wreckages"], "11.4 6.9 21.2": ["graters"], "7.4 0.8 8.3": ["screenprints"], "4.4 9.5 11.5": ["asbo"], "11.1 2.1 20.8": ["sizzlin"], "14.8 18.5 14.9": ["exo"], "8.8 13.2 9.7": ["grittily"], "12.4 3.4 14.6": ["bambino"], "17.5 10.9 11.8": ["kludge"], "7.5 11.1 12.4": ["hic"], "8.3 6.0 14.5": ["intoxicatingly"], "3.1 -4.2 15.4": ["fod"], "2.2 5.3 8.9": ["glamping"], "5.3 17.5 10.0": ["corrosives"], "-7.6 4.8 8.4": ["restaveks"], "11.6 17.8 20.8": ["nightingales"], "2.3 2.4 4.2": ["geotextiles"], "-4.0 11.0 15.4": ["nani"], "8.5 0.8 9.7": ["gli"], "9.2 -5.0 11.1": ["nj"], "-0.4 5.1 14.4": ["anglos"], "6.0 17.5 3.2": ["surveilance"], "19.5 3.7 17.7": ["shufflers"], "12.2 0.1 13.6": ["stockfeed"], "13.0 7.2 9.1": ["fullsize"], "0.4 8.3 15.5": ["maka"], "3.6 18.7 -4.0": ["concertedly"], "2.6 6.4 8.3": ["horological"], "6.7 -0.0 10.6": ["montreal"], "-1.8 4.3 8.0": ["oenology"], "-5.6 7.7 3.3": ["contextualizes"], "4.0 17.0 4.1": ["befool"], "-2.1 8.8 12.0": ["abhinaya"], "15.4 11.3 9.1": ["canniest"], "6.1 18.6 18.9": ["motile"], "3.3 16.9 17.5": ["krump"], "-0.3 12.6 2.9": ["poleman"], "12.5 14.6 9.5": ["superphones"], "13.7 8.5 18.0": ["biggy"], "6.0 12.8 31.4": ["pescado"], "7.9 16.7 8.1": ["leftwingers"], "10.2 7.0 24.8": ["sweetmeat"], "3.2 7.3 4.7": ["drivelines"], "8.5 9.3 5.2": ["pleasured"], "-2.6 18.5 22.0": ["broadhead"], "7.4 9.2 19.7": ["bowers"], "2.7 3.2 12.0": ["francais"], "6.7 0.8 8.9": ["presse"], "14.9 12.8 11.2": ["lecher"], "18.8 19.1 9.8": ["doppleganger"], "-1.5 10.3 2.5": ["productiveness"], "-1.4 2.2 11.4": ["hyperparathyroidism"], "-7.9 3.9 8.2": ["immunohistochemical"], "-14.5 1.7 -1.1": ["kollel"], "19.9 7.8 17.6": ["scraggy"], "0.2 4.6 53.6": ["porgy"], "9.0 8.0 13.7": ["campo"], "4.7 10.0 10.6": ["repetoire"], "-9.0 11.5 43.1": ["fluking"], "3.4 11.0 9.2": ["wordly"], "-2.6 10.3 10.2": ["quatrains"], "14.5 5.7 23.2": ["palapa"], "4.0 10.5 5.3": ["goaline"], "20.5 16.8 3.8": ["techonology"], "15.5 18.3 25.9": ["melaleuca"], "-0.5 8.9 4.4": ["guiltiest"], "11.9 3.4 13.0": ["resturants"], "5.8 6.3 22.4": ["tablescape"], "1.3 3.5 -2.5": ["appealling"], "-3.1 5.7 9.7": ["dannii"], "7.7 4.7 8.8": ["jobcentre"], "9.9 -0.1 -7.3": ["thenew"], "-1.4 -1.0 10.4": ["colourways"], "9.0 4.9 4.4": ["shoul"], "-11.2 4.7 15.7": ["folkstyle"], "5.0 6.7 35.6": ["tamari"], "-4.6 5.2 8.7": ["triazole"], "-1.2 8.9 5.5": ["defintion"], "1.0 -2.5 5.3": ["videocasts"], "6.2 8.0 8.0": ["rightsize"], "4.0 6.9 7.4": ["tmp"], "11.7 4.3 15.2": ["sumptuousness"], "6.1 5.3 5.6": ["fas"], "3.0 16.8 8.1": ["tattled"], "-5.9 5.7 10.3": ["kendra"], "19.1 -2.3 -2.0": ["naar"], "2.0 8.6 9.1": ["toppish"], "1.8 5.2 6.4": ["cageside"], "12.3 2.4 24.6": ["frypan"], "11.3 4.6 9.1": ["ensuites"], "-3.3 1.6 1.6": ["intrested"], "12.0 7.3 5.3": ["grooviest"], "4.6 15.2 5.5": ["oscillatory"], "4.9 7.1 3.1": ["transfusing"], "9.2 32.2 14.4": ["merc"], "11.1 5.6 15.4": ["bothy"], "18.8 -1.3 11.8": ["gurgler"], "5.5 14.9 8.5": ["tbh"], "-6.5 -3.5 13.2": ["gonadotropin"], "22.3 7.7 2.8": ["shedloads"], "4.4 8.9 10.1": ["appal"], "-0.3 4.8 18.3": ["saison"], "-1.0 12.1 8.4": ["endophthalmitis"], "0.8 16.2 1.2": ["desensitisation"], "2.9 11.2 8.2": ["wises"], "2.9 9.4 -5.1": ["jubilate"], "4.0 12.4 11.9": ["glock"], "15.6 14.4 0.6": ["advergame"], "1.9 11.2 5.5": ["allocator"], "-0.1 12.3 4.0": ["circuitously"], "15.5 9.5 15.5": ["brewskis"], "8.6 -6.3 8.5": ["contined"], "5.6 9.5 27.1": ["banca"], "7.4 6.4 8.3": ["fergie"], "2.6 12.3 13.6": ["ehrlichiosis"], "0.0 2.5 15.1": ["kanya"], "11.2 9.2 14.1": ["merde"], "-2.7 9.9 13.2": ["aam"], "-5.3 1.7 11.2": ["achondroplasia"], "3.2 3.1 8.8": ["incenting"], "4.8 5.7 15.5": ["pressies"], "3.8 14.6 5.7": ["trequartista"], "13.8 7.8 21.0": ["rita"], "7.9 14.8 -0.3": ["antonyms"], "5.6 15.4 4.1": ["rivarly"], "-1.1 18.1 6.8": ["gameplanning"], "0.3 7.8 6.4": ["miseducation"], "8.1 6.6 22.7": ["carnelian"], "1.3 9.6 1.9": ["sufferable"], "18.2 1.2 20.8": ["tasselled"], "-3.3 11.8 13.5": ["houseless"], "5.5 10.2 16.6": ["celexa"], "9.4 7.5 11.5": ["tatts"], "-1.6 3.8 -2.9": ["traning"], "0.9 9.5 0.9": ["connexion"], "4.9 4.7 16.7": ["papules"], "10.7 18.6 13.2": ["wooziness"], "-0.9 3.6 15.7": ["flyash"], "1.9 -0.5 7.1": ["tant"], "17.8 7.2 5.3": ["cybersquatter"], "-13.0 6.0 -2.1": ["fibrinolysis"], "12.8 -1.6 9.9": ["goh"], "6.2 11.5 13.6": ["upthecherries"], "-0.3 7.8 3.3": ["nonfootball"], "16.3 4.3 6.3": ["bioresearch"], "5.2 3.8 24.5": ["jenny"], "-3.6 5.9 2.8": ["monetizations"], "8.8 10.0 19.4": ["bandsaw"], "1.2 9.2 45.7": ["kahawai"], "-1.5 11.1 -1.7": ["jubilates"], "-0.4 -2.9 2.0": ["renewability"], "-5.9 6.3 9.0": ["medicalized"], "7.4 10.0 7.1": ["employe"], "0.0 1.8 10.6": ["stu"], "9.9 13.1 10.4": ["lurve"], "-2.6 12.8 10.6": ["contagiousness"], "-1.6 7.8 0.9": ["superscript"], "7.8 9.5 11.7": ["microfibers"], "-4.6 20.6 2.3": ["scripturally"], "15.8 5.3 17.3": ["rific"], "11.3 16.4 10.9": ["shorters"], "1.3 10.6 -0.1": ["lbf"], "14.2 4.7 10.3": ["cadge"], "13.0 7.8 10.1": ["pasteboard"], "3.7 9.4 6.3": ["unneccesary"], "2.2 8.0 6.3": ["highline"], "6.3 15.8 8.7": ["daredevilry"], "4.4 0.9 15.1": ["amto"], "15.7 6.4 6.2": ["sandblaster"], "-0.8 3.6 8.5": ["undisrupted"], "10.4 -0.1 4.8": ["teleshopping"], "-1.9 5.5 7.5": ["sabhas"], "14.5 7.5 8.5": ["nanosized"], "9.8 15.7 15.6": ["shotgunning"], "1.7 3.4 3.4": ["fampridine"], "7.9 7.0 17.9": ["tumescent"], "-3.8 4.7 0.5": ["intersted"], "23.5 7.9 23.4": ["mirrorball"], "14.9 5.8 5.5": ["deregulations"], "6.4 6.9 27.8": ["ambergris"], "11.9 9.0 32.0": ["sriracha"], "-2.7 13.7 6.1": ["paroxysmal"], "2.4 10.7 14.5": ["diggs"], "-5.1 -2.0 2.9": ["sayd"], "-3.2 2.8 1.6": ["df"], "3.4 7.5 -4.4": ["managerially"], "5.3 -3.6 4.4": ["nni"], "3.0 7.8 23.0": ["anoxia"], "3.9 6.8 13.3": ["unexplainably"], "11.1 11.4 17.6": ["darkish"], "4.9 6.7 20.1": ["highballs"], "6.6 16.6 21.3": ["biotoxins"], "23.9 5.5 41.0": ["gannet"], "13.5 10.6 7.5": ["chatterers"], "3.7 10.8 8.0": ["longueurs"], "14.8 15.4 14.1": ["awwww"], "12.8 16.0 12.5": ["corniest"], "4.4 6.5 13.6": ["sweatin"], "-5.8 12.7 8.9": ["bailiwicks"], "8.6 7.8 18.8": ["relict"], "11.0 11.0 20.5": ["coulees"], "8.0 3.4 10.4": ["disruptively"], "-4.3 7.5 -0.2": ["ommission"], "9.1 -0.3 9.7": ["trashier"], "-1.8 4.5 11.6": ["mayoralties"], "8.1 10.1 11.8": ["baaack"], "8.7 1.4 3.2": ["deze"], "0.9 10.6 8.6": ["ubiquitination"], "15.0 16.5 14.3": ["noisemaking"], "8.2 9.8 9.8": ["moviehouse"], "8.9 13.7 18.6": ["snowpocalypse"], "15.1 22.5 14.8": ["wiley"], "17.1 8.6 10.8": ["unhurriedly"], "-2.2 9.7 9.1": ["talmudic"], "3.0 8.5 4.0": ["unexperienced"], "7.8 8.8 2.4": ["editorialised"], "6.4 16.1 11.9": ["windspeed"], "10.0 -5.8 11.3": ["aheads"], "7.0 15.9 26.8": ["pistil"], "14.1 -0.1 -2.5": ["reprocesses"], "15.1 10.5 17.3": ["widdle"], "10.2 3.9 3.7": ["cyl"], "28.2 15.5 7.4": ["corkscrewing"], "23.0 19.4 8.5": ["lightless"], "2.7 8.9 16.0": ["beryl"], "-8.6 11.2 -0.7": ["superdoofus"], "-7.2 8.2 20.8": ["subarea"], "7.3 3.8 5.0": ["pershare"], "9.4 13.6 14.8": ["pitty"], "1.4 6.0 3.1": ["condusive"], "9.7 5.7 28.6": ["lavash"], "-4.0 16.1 8.2": ["overacts"], "3.1 16.5 13.4": ["keyphrases"], "10.9 7.3 6.6": ["corporatise"], "4.0 19.1 4.1": ["allout"], "7.7 9.1 14.2": ["armholes"], "7.4 9.2 22.4": ["blackbuck"], "5.1 4.6 -0.7": ["finetuned"], "2.0 0.2 20.1": ["gamete"], "6.3 5.7 23.1": ["chapatti"], "19.8 18.7 34.8": ["nibblers"], "17.8 6.0 5.8": ["plushest"], "-6.1 4.7 6.8": ["cystectomy"], "16.0 12.6 6.4": ["jittering"], "-8.6 10.1 3.7": ["visitng"], "19.5 18.5 12.0": ["petard"], "12.8 2.2 6.3": ["futurologist"], "11.1 10.1 8.0": ["dunning"], "16.9 14.5 15.7": ["winky"], "0.1 7.4 7.6": ["oxidase"], "2.9 13.2 12.9": ["locutions"], "-7.9 6.8 12.1": ["proteolysis"], "7.5 6.0 10.9": ["dup"], "-0.7 -2.1 4.4": ["distillations"], "1.5 -1.3 9.3": ["ethylbenzene"], "11.8 9.6 9.0": ["casey"], "1.1 14.0 15.5": ["underthrow"], "8.6 6.9 4.9": ["crossbench"], "1.3 4.3 4.4": ["pertuzumab"], "-6.8 3.8 11.3": ["showband"], "13.9 16.6 9.2": ["bemuse"], "-3.8 12.0 5.6": ["juristic"], "6.2 -1.5 6.0": ["interconnectors"], "15.2 3.4 22.6": ["baja"], "9.1 10.0 5.7": ["southwestward"], "1.8 9.8 4.9": ["epsilon"], "0.4 12.2 4.9": ["comported"], "1.9 13.0 10.3": ["fictionalizing"], "6.2 5.6 11.4": ["hiccupped"], "0.5 12.2 23.3": ["pakeha"], "-3.2 13.7 3.6": ["keyframes"], "10.1 5.2 40.5": ["etouffee"], "8.1 7.7 14.9": ["loungey"], "7.8 16.6 24.9": ["daggerboard"], "6.8 6.2 4.1": ["unstrapped"], "10.9 34.6 0.1": ["gunsight"], "3.4 11.2 18.8": ["setts"], "9.4 10.0 14.6": ["lamina"], "14.0 11.3 2.9": ["anticapitalist"], "-2.4 -3.8 6.0": ["erven"], "10.1 8.0 9.5": ["deftest"], "5.3 -0.5 10.4": ["popera"], "7.8 4.9 2.5": ["regenerator"], "5.8 18.5 6.7": ["brotherliness"], "4.5 18.0 8.3": ["cussedness", "highbrows"], "-2.5 10.6 -0.8": ["scintigraphy"], "4.8 14.0 2.3": ["precognition"], "17.2 8.5 16.4": ["bungy"], "2.8 15.7 5.7": ["eulogists"], "3.6 -0.3 3.7": ["endof"], "8.7 -2.1 6.9": ["reupholster"], "-3.0 13.8 2.7": ["neuroanatomy"], "2.1 3.0 -5.5": ["thebest"], "0.5 -3.3 4.4": ["somatropin"], "16.0 7.9 10.1": ["unwire"], "3.1 0.1 4.0": ["cath"], "-4.9 -5.6 6.5": ["cochaired"], "2.1 17.2 18.5": ["slaughterers"], "2.2 6.4 12.7": ["myositis"], "10.7 9.6 15.0": ["freegans"], "-0.4 3.5 -0.6": ["excell"], "11.1 7.6 14.2": ["namers"], "12.5 10.2 30.3": ["capuchin"], "-3.8 19.9 12.9": ["infinitesimally"], "-6.3 13.2 2.9": ["prejudges"], "3.6 9.4 9.1": ["deracinated"], "14.7 9.7 -1.4": ["robotized"], "4.7 -2.1 13.3": ["shay"], "0.5 11.7 22.9": ["drydocks"], "3.5 12.6 7.3": ["shotblocker"], "15.3 11.2 12.6": ["henge"], "8.7 11.8 21.2": ["deadest"], "8.9 3.4 7.7": ["bathetic"], "11.9 9.6 3.1": ["upclose"], "15.2 4.6 5.8": ["aaahs"], "-5.7 1.4 2.5": ["otolaryngologists"], "-7.9 6.7 4.5": ["diltiazem"], "3.4 10.8 16.0": ["sherriff"], "-9.6 7.8 7.6": ["rideout"], "14.3 6.0 9.7": ["servomotors"], "12.5 -2.5 13.1": ["dex"], "-4.1 -7.3 -1.4": ["recived"], "-5.2 1.2 5.0": ["filgrastim"], "5.8 4.3 5.8": ["recode", "bood"], "-1.1 4.4 6.4": ["associativity"], "12.9 17.0 3.7": ["sweatiest"], "10.1 -3.2 16.7": ["ceili"], "14.4 11.9 4.8": ["ultramobile"], "0.5 14.1 6.6": ["boks"], "2.7 3.8 10.9": ["playtimes"], "9.3 4.0 22.0": ["monstrance"], "7.8 6.2 11.1": ["khana"], "0.0 14.4 11.6": ["spoilery"], "7.6 -0.6 6.8": ["phonelines"], "9.6 17.2 2.3": ["unbalances"], "6.1 -3.3 3.5": ["spoked"], "22.5 11.6 4.2": ["jawdropping"], "8.7 -0.6 45.9": ["sprats"], "8.4 13.2 5.3": ["braches"], "9.3 4.1 14.4": ["recirculates"], "-3.9 4.1 7.0": ["sadi"], "-9.6 -1.2 -5.5": ["athough"], "2.4 7.4 14.4": ["ninyo"], "-1.6 5.9 6.7": ["checkmarks"], "8.5 0.1 11.5": ["reusables"], "-1.5 8.2 17.5": ["mockumentaries"], "14.6 11.5 10.4": ["hazes"], "-8.0 5.8 2.5": ["councilpersons"], "-1.9 7.4 9.9": ["dillydallying"], "5.9 6.6 14.8": ["yor"], "8.6 11.8 39.3": ["scoters"], "17.9 15.8 17.0": ["indecisively"], "-2.7 25.6 12.9": ["thereat"], "14.0 -0.2 7.8": ["jitterbugging"], "8.1 13.0 12.1": ["enuff"], "7.5 9.4 8.6": ["packable"], "13.5 6.9 7.9": ["streetcorner"], "15.1 10.0 12.7": ["webby"], "7.9 13.6 6.6": ["dehumidifying"], "15.7 1.3 13.8": ["gogo"], "1.2 0.5 -4.2": ["abas"], "1.4 10.7 8.8": ["handpumps"], "-2.4 18.9 9.5": ["contendership"], "8.5 12.8 19.1": ["methanogens"], "11.0 20.1 14.1": ["bandolier"], "8.2 9.5 7.9": ["slided"], "2.9 7.2 4.5": ["unti"], "12.3 2.5 12.5": ["syphilitic"], "8.1 10.8 38.9": ["pepperoncini"], "19.1 8.8 10.6": ["deregulates"], "-5.6 7.6 7.9": ["andante"], "-0.7 17.8 9.0": ["adrenals"], "1.0 2.3 6.9": ["grindingly"], "12.6 0.9 8.9": ["commmunity"], "4.6 7.4 5.5": ["trocar"], "7.8 17.2 5.2": ["boastfulness"], "16.4 9.4 19.9": ["guidette"], "7.0 9.5 22.1": ["footgear"], "21.5 18.7 13.9": ["snooper"], "2.5 0.1 15.6": ["mahalo"], "6.8 14.9 9.2": ["oppertunity"], "0.9 17.3 19.6": ["sawfly"], "0.8 6.9 14.9": ["novenas"], "10.9 16.5 19.7": ["nads"], "-0.7 7.4 15.2": ["pcb"], "4.1 16.1 6.1": ["marketization"], "1.6 6.0 5.0": ["benedictions"], "21.6 -2.6 16.4": ["facepainting"], "-0.1 2.9 7.3": ["scoresheets"], "8.0 4.4 19.4": ["shorthair"], "15.2 27.7 3.9": ["pretexters"], "2.6 -5.4 12.6": ["restrung"], "2.1 4.3 3.1": ["deforolimus"], "7.8 12.5 22.7": ["dao"], "13.9 6.8 43.2": ["bloodworm"], "21.7 10.4 25.4": ["goanna"], "10.2 4.6 -2.1": ["andis"], "-4.6 7.7 7.9": ["catalase"], "2.8 3.4 -5.0": ["preselect"], "3.1 13.5 13.9": ["northen"], "3.9 8.4 40.4": ["favas"], "5.3 14.0 3.7": ["attaboys"], "0.3 15.2 9.0": ["outboxing"], "6.3 17.2 29.8": ["seawaters"], "-0.8 2.5 5.0": ["superintended"], "10.9 3.6 0.8": ["repots"], "3.7 6.2 10.5": ["suggestiveness"], "16.7 -0.7 6.2": ["hiccuped"], "-0.5 16.6 1.3": ["detectible"], "-2.0 3.8 4.5": ["transcoders"], "12.6 12.0 19.3": ["chuggers"], "10.4 23.0 9.5": ["federales"], "10.1 10.1 28.2": ["aquavit"], "-4.8 17.3 5.5": ["likelihoods"], "1.8 4.4 8.3": ["housemother"], "3.1 6.0 8.5": ["phlebitis", "outpitches"], "-3.1 7.4 5.0": ["parecon"], "6.4 12.4 7.7": ["guber"], "-5.4 7.3 4.5": ["scenarist"], "27.9 7.1 28.8": ["wriggly"], "-8.2 20.7 -0.5": ["madressah"], "10.1 7.6 8.3": ["protractors"], "14.4 9.4 12.6": ["boxcutter"], "9.2 11.1 16.0": ["planetesimals"], "-1.3 19.1 -0.2": ["newsitems"], "-3.9 4.1 8.1": ["osteolysis"], "-2.0 15.5 20.1": ["poxvirus"], "13.2 10.8 7.8": ["pushin"], "7.9 4.4 7.0": ["isexpected"], "-1.9 5.3 9.2": ["overexpressing"], "17.0 9.9 7.6": ["starkers"], "-0.6 6.6 9.4": ["cpus"], "3.6 -0.7 7.1": ["wimax"], "-1.3 10.4 13.5": ["salicylates"], "12.6 4.1 13.2": ["scaffolders"], "6.6 8.5 -1.5": ["buring"], "16.2 13.9 17.2": ["spiller"], "1.4 3.2 -3.1": ["unbanning"], "11.5 11.2 10.8": ["raggedly"], "2.3 1.7 16.4": ["rubdowns"], "0.4 9.6 7.3": ["recoverd"], "3.1 13.6 15.6": ["holdin"], "0.8 2.0 14.3": ["layaways"], "7.3 4.7 38.9": ["lardons"], "7.2 3.5 -0.3": ["outlicensing"], "8.3 14.5 12.9": ["nightime"], "3.4 -1.4 2.7": ["webshop"], "11.8 11.1 15.5": ["fla"], "8.9 4.6 0.5": ["respondants"], "13.2 1.5 9.7": ["taranabant"], "13.4 3.1 12.0": ["sitars"], "-13.0 7.9 5.6": ["zina"], "12.8 15.8 14.2": ["fissured"], "6.3 6.5 11.8": ["instrumentations"], "20.7 10.6 21.0": ["diametre"], "5.2 10.0 9.9": ["teamwide"], "14.0 8.5 26.0": ["lovebird"], "2.4 7.2 12.8": ["bharatanatyam"], "16.8 6.3 15.1": ["tatooed"], "7.4 19.1 4.9": ["supercell"], "16.4 9.7 12.0": ["whinnying"], "8.6 10.9 12.8": ["forbiddingly"], "3.1 7.7 8.5": ["pere"], "8.1 6.0 28.7": ["gonad"], "-2.3 16.2 14.9": ["intersexed"], "16.1 10.7 20.6": ["vegemite"], "-3.1 14.1 13.3": ["patwari"], "3.7 -0.1 17.0": ["dolphinarium"], "14.0 4.6 22.1": ["munchie"], "0.6 12.5 20.9": ["liferafts"], "-3.8 11.7 -1.3": ["candiate"], "11.6 8.3 20.6": ["reheats"], "8.3 5.0 12.6": ["waggish"], "-0.3 -3.4 11.2": ["groupset"], "4.9 9.4 14.6": ["stampers"], "1.0 2.8 6.8": ["ett"], "15.9 17.3 7.4": ["immobilising"], "5.2 9.4 35.5": ["molted"], "10.8 -6.6 -5.0": ["irst"], "-4.5 23.8 6.7": ["intifadah"], "-2.5 16.7 17.2": ["backbreakers"], "31.4 8.8 9.5": ["telcoms"], "4.7 17.5 13.6": ["interrelatedness"], "3.9 2.4 10.9": ["vince"], "-0.1 -2.0 8.4": ["prepregs"], "-1.2 9.1 11.7": ["cheekpieces"], "-6.0 0.3 3.2": ["meperidine"], "18.2 4.2 16.4": ["uncoiling"], "-4.0 12.5 6.8": ["walkaways"], "1.0 12.3 11.2": ["stylesheet"], "9.1 12.0 5.9": ["dobbing"], "-4.4 1.2 0.1": ["preparative"], "13.0 5.0 6.3": ["greece"], "0.7 13.0 5.3": ["ablated"], "9.7 13.9 25.7": ["corky"], "-7.3 1.6 11.2": ["exceedance"], "4.1 16.2 1.4": ["reframes"], "-3.1 10.5 3.5": ["detent"], "-13.4 5.3 -0.6": ["ventilatory"], "10.1 18.4 9.8": ["impenetrability"], "-4.2 21.6 5.6": ["remobilize"], "16.3 10.1 45.1": ["chanterelle"], "1.0 -6.1 -0.8": ["biostatisticians"], "-0.6 17.8 15.2": ["overswinging"], "3.9 11.2 8.4": ["titillates"], "5.4 13.0 -3.3": ["intercommunication"], "1.2 11.9 13.9": ["singaporeans"], "15.5 9.2 13.9": ["twinks"], "8.6 4.7 12.8": ["billfolds"], "16.6 12.4 9.5": ["doomsters"], "-13.3 8.6 6.9": ["dysthymia"], "16.3 10.7 -2.1": ["synonomous"], "9.7 0.6 14.9": ["steller"], "8.9 3.6 -3.4": ["derecognise"], "15.1 8.3 4.9": ["testbeds"], "1.2 4.6 16.4": ["baches"], "0.5 12.4 10.2": ["monolayers"], "1.7 1.7 8.1": ["comperes"], "-6.4 15.2 11.7": ["contrabands"], "5.1 5.7 -4.9": ["prognostics"], "17.9 12.2 15.1": ["thundersticks"], "-3.7 9.8 7.5": ["sendmail"], "3.0 15.7 7.7": ["oga"], "10.8 4.4 15.8": ["mixi", "burek"], "8.2 9.7 27.0": ["cornflower"], "-0.4 5.8 1.8": ["intraperitoneal"], "5.3 16.5 12.8": ["beatitudes"], "7.6 21.1 14.9": ["revenuers"], "2.0 5.1 32.2": ["mirepoix"], "14.4 15.4 15.9": ["knolls"], "4.3 12.3 14.7": ["artifacting"], "7.7 -1.5 4.6": ["frequenters"], "5.5 7.1 11.2": ["epididymis"], "-9.0 0.8 13.1": ["phytate"], "2.6 6.9 35.3": ["bechamel"], "5.8 8.4 14.5": ["metrosexuality"], "2.8 10.2 2.2": ["staight"], "3.8 0.8 4.1": ["rupiahs"], "0.5 11.3 6.6": ["unenlightening"], "-0.2 -1.5 1.8": ["qubo"], "-2.6 -2.8 -4.0": ["proctoring"], "15.3 -0.6 7.4": ["unblocks"], "7.4 11.4 12.5": ["huggy"], "-2.9 5.3 1.7": ["unconflicted"], "1.1 6.3 1.2": ["spectrographs"], "-10.0 8.5 10.2": ["lectionary"], "-0.5 0.4 12.6": ["birthstones"], "6.2 18.8 14.8": ["bigotries"], "13.2 0.4 7.9": ["petcare"], "13.9 11.8 18.3": ["setae"], "-3.6 7.3 12.2": ["refigure"], "0.9 4.5 16.4": ["rusticity"], "2.9 12.1 9.5": ["artforms"], "18.7 9.4 3.0": ["cartloads"], "11.0 11.3 4.1": ["antitheft"], "12.8 1.3 5.1": ["pesetas"], "3.6 10.2 6.0": ["phonological"], "2.1 9.7 14.4": ["simula"], "21.9 11.4 15.6": ["niftily"], "1.8 21.4 4.5": ["indecencies"], "-1.7 -2.4 7.2": ["teleplays"], "17.7 11.4 13.4": ["washerwoman"], "5.9 1.4 17.4": ["coving"], "-2.9 1.8 -5.3": ["depo"], "9.9 28.6 14.6": ["generalissimo"], "-0.9 2.4 18.2": ["hab"], "-6.3 8.9 8.2": ["consistancy"], "0.8 15.6 7.0": ["racecraft"], "1.3 6.4 4.2": ["efficacies"], "14.0 30.6 25.7": ["yellowjackets"], "5.1 13.2 9.7": ["incrementing"], "5.9 7.3 6.8": ["canoodled"], "5.2 34.6 5.9": ["zionists"], "-7.2 17.2 5.4": ["ruggedization"], "0.2 2.9 9.3": ["tyler"], "-0.1 10.3 12.7": ["headiness"], "3.8 20.9 1.1": ["oxidizers"], "21.7 0.1 7.5": ["razzamatazz"], "8.8 16.8 13.5": ["birthrights"], "1.4 7.8 12.5": ["goalkicks"], "-3.1 7.1 4.5": ["reboost"], "6.7 21.8 5.6": ["disseminators"], "-3.8 5.9 5.5": ["chol"], "-1.4 5.8 5.1": ["sitarist"], "-9.2 3.8 4.2": ["subadvisor"], "-4.0 12.4 7.3": ["canonically"], "1.0 9.2 9.4": ["shiftier"], "-9.9 3.9 -0.4": ["ethanolamines"], "16.1 7.0 -1.1": ["leaser"], "2.8 9.7 2.0": ["btwn"], "12.8 10.6 20.1": ["gunge"], "13.7 16.9 16.1": ["indelicately"], "-1.4 14.6 13.1": ["multicandidate"], "1.6 20.8 2.7": ["signally"], "17.4 18.3 17.1": ["housecats"], "0.9 8.9 8.4": ["gurudwaras"], "15.0 15.3 15.9": ["paddleball"], "19.9 19.2 22.0": ["glowy"], "9.9 3.1 12.9": ["bioactives"], "3.7 4.1 -1.9": ["gegen"], "9.9 -2.7 13.9": ["env"], "6.4 17.5 5.7": ["inveigle"], "11.5 15.7 28.3": ["longboats"], "10.3 7.3 -0.5": ["energywatch"], "-9.9 10.0 9.1": ["basehits"], "11.2 17.3 14.4": ["slewing"], "-3.5 12.8 1.2": ["allopathy"], "0.2 17.1 8.0": ["asparagine"], "-4.7 6.3 0.8": ["biodistribution"], "6.1 2.3 10.5": ["aftershow"], "9.2 9.2 2.3": ["kludgy"], "1.0 12.4 7.0": ["eroticized"], "5.3 14.7 18.5": ["zoysia"], "-2.7 2.9 6.7": ["elapsing"], "11.2 18.4 18.5": ["leglock"], "6.8 20.1 10.3": ["eyeline"], "10.5 10.2 9.5": ["faff"], "0.4 8.8 8.7": ["intercellular"], "13.2 7.7 1.8": ["unchain"], "3.0 2.2 11.8": ["kathy"], "-1.7 0.6 9.1": ["tubal"], "-0.6 16.1 17.5": ["spalling"], "8.6 0.7 8.5": ["guranteed"], "6.8 4.8 4.8": ["superfluity"], "0.6 15.2 11.6": ["dishdasha"], "-4.4 2.8 6.2": ["eszopiclone"], "-2.0 21.4 5.7": ["hypervigilance"], "4.2 -4.9 7.7": ["monthy"], "-3.9 -1.5 3.2": ["revisitation"], "17.2 5.6 22.2": ["effluvia"], "-1.2 8.4 13.1": ["squalamine"], "6.8 8.8 8.8": ["rivetting"], "2.5 8.7 -0.6": ["radiotracer"], "9.8 12.6 23.2": ["dodder"], "0.2 8.7 24.9": ["barbecuers"], "5.6 4.5 4.1": ["valuator"], "8.7 3.4 40.4": ["mulloway"], "3.4 16.1 9.0": ["flagyl"], "8.9 9.5 22.8": ["madeleine"], "1.8 5.1 7.7": ["dehedging"], "9.2 11.3 26.8": ["pao"], "12.6 6.7 6.3": ["darkrooms"], "-0.8 6.7 -1.5": ["apomorphine"], "-8.3 12.9 4.4": ["suggestibility"], "1.9 7.7 13.6": ["bioswales"], "2.3 18.3 7.0": ["individuation"], "8.9 14.6 12.4": ["puling"], "5.2 2.8 6.5": ["sextape"], "2.5 4.0 -0.1": ["eines"], "4.1 14.2 11.0": ["gluteus"], "11.8 12.1 17.1": ["continentals"], "8.8 7.5 11.3": ["nocturne"], "-9.0 14.2 -0.2": ["inflamatory"], "6.2 4.6 10.9": ["bumpiest"], "-5.6 -2.5 5.9": ["imipramine"], "9.1 1.8 5.8": ["hq"], "8.1 25.9 13.3": ["seducers"], "12.8 5.3 8.7": ["onland"], "-1.3 4.9 9.5": ["nonlawyer"], "14.0 7.8 6.8": ["insecurely"], "12.9 18.0 13.4": ["wimping"], "10.6 9.1 7.8": ["ethnographers"], "5.2 12.9 2.0": ["grisliest"], "-2.3 15.7 9.9": ["crits"], "-2.6 8.0 5.7": ["endodontist"], "9.7 18.5 10.3": ["ratbag"], "10.1 10.8 16.2": ["callouses"], "5.6 6.3 4.3": ["tpm"], "4.9 19.9 5.1": ["bureaucratized"], "-0.3 -2.9 0.5": ["sexology"], "-1.1 13.2 6.4": ["teamate"], "-5.7 8.9 8.5": ["numismatist"], "3.4 20.4 0.8": ["theirselves"], "-6.6 11.8 0.2": ["harrasment"], "23.8 24.9 26.8": ["velociraptors"], "15.2 18.2 9.0": ["grotesqueries"], "7.5 16.6 7.7": ["tarried"], "-3.9 0.1 13.0": ["superannuitants"], "2.9 4.0 4.3": ["dv"], "5.4 13.0 3.4": ["retargeted"], "-1.5 1.9 16.7": ["bpa"], "2.6 14.2 6.9": ["airflows"], "14.0 9.8 20.5": ["wrasslin"], "-4.8 8.0 6.7": ["univariate"], "8.8 4.4 20.8": ["chaw"], "19.0 -2.1 11.4": ["softdrinks"], "4.3 24.7 19.5": ["bollworms"], "6.9 26.4 4.5": ["shellings"], "-1.9 5.4 6.9": ["unblinding"], "7.5 8.2 15.6": ["histidine"], "21.4 13.1 4.8": ["aigo"], "8.0 4.7 14.1": ["monzonite"], "0.2 15.0 10.6": ["metalforming"], "1.4 17.0 18.5": ["carbaryl"], "3.5 13.8 34.9": ["habaneros"], "23.9 6.7 16.5": ["minature"], "12.6 2.4 11.0": ["parcelling"], "2.7 2.4 18.7": ["lamang"], "5.4 11.8 0.4": ["quiting"], "8.2 5.5 13.5": ["bioassays"], "6.7 6.3 13.4": ["obestatin"], "7.2 26.2 9.4": ["inmost"], "1.4 7.4 10.0": ["retractors"], "-0.9 7.1 8.9": ["scrapbooker"], "-7.7 11.5 2.7": ["unliquidated"], "0.1 4.1 -6.3": ["chastized"], "-1.6 4.1 7.3": ["engrafted"], "-4.3 31.6 10.1": ["wargaming"], "-1.7 10.4 32.3": ["nymphing"], "4.0 10.0 3.3": ["nanomechanical"], "-2.9 18.0 3.1": ["cognitions"], "2.5 33.2 18.7": ["mutineer"], "3.9 6.4 17.2": ["glans"], "13.7 5.1 -3.4": ["xref"], "7.9 17.0 22.4": ["headsails"], "13.7 -1.8 9.2": ["bandstands"], "5.5 13.7 9.9": ["interferometers"], "12.3 11.7 20.0": ["pennywise"], "11.1 18.9 3.0": ["destructing"], "22.2 -2.0 5.9": ["biopharm"], "7.3 5.1 16.7": ["jill"], "12.5 14.2 12.2": ["smilin"], "-2.0 10.4 4.2": ["quadrupole"], "10.5 11.8 4.0": ["heavyhanded"], "3.3 8.9 7.3": ["heteros"], "-2.9 4.8 5.9": ["pegylated"], "2.0 17.5 6.6": ["declaims"], "5.9 20.4 28.6": ["hogweed"], "8.9 9.1 10.2": ["effusiveness"], "7.9 0.5 3.0": ["fazing"], "4.2 -0.8 -4.7": ["rtg"], "5.6 8.2 6.9": ["salaciousness"], "7.1 16.9 23.9": ["southerlies"], "2.2 9.3 0.5": ["beatifying"], "8.5 -4.5 6.8": ["pennsylvania"], "-0.4 8.1 3.8": ["cabazitaxel"], "2.3 13.6 13.0": ["chavista"], "-4.5 6.3 -2.1": ["capacitated"], "-4.6 1.7 8.3": ["perming"], "28.6 17.7 3.2": ["bestrides"], "9.7 13.8 21.6": ["euphorbia"], "0.1 11.0 0.1": ["unshakably"], "4.8 3.9 12.6": ["eurodollar"], "15.2 12.6 11.0": ["goldminers"], "8.5 8.3 16.4": ["landladies"], "-10.2 5.9 -4.5": ["neuropsychiatrist"], "-2.9 11.1 6.1": ["vocalise"], "3.0 14.6 13.8": ["transshipments"], "9.7 0.3 9.8": ["drawbar"], "4.9 13.3 0.5": ["dunned"], "16.9 11.7 6.1": ["twerps"], "-7.4 24.1 -2.8": ["jamaat"], "1.9 8.1 -3.4": ["responible"], "9.2 6.7 6.5": ["unordered"], "3.0 13.5 8.2": ["enantiomers"], "12.8 -7.3 -2.2": ["queered"], "5.4 16.0 29.3": ["hellebore"], "13.1 3.6 10.4": ["stonecutter"], "-9.5 6.4 9.2": ["unobligated"], "7.0 0.9 -0.6": ["dematerialization"], "12.2 16.3 15.1": ["gesticulation"], "4.2 -1.8 12.2": ["oddments"], "0.3 9.1 11.2": ["riad"], "8.2 9.9 13.0": ["ppp"], "-7.4 16.7 3.4": ["iman"], "10.0 0.9 20.6": ["kanga"], "-0.5 3.2 18.3": ["stockiest"], "-4.8 14.6 12.0": ["glenoid"], "4.0 6.4 16.8": ["serge"], "10.9 11.1 20.5": ["warmish"], "3.9 5.5 3.7": ["metathesis"], "11.5 11.3 19.6": ["skanking"], "-1.3 -6.8 6.3": ["util"], "-0.8 7.5 14.3": ["laudanum"], "5.0 1.8 8.8": ["carillonneur"], "-2.0 -0.3 -1.7": ["earler"], "1.4 15.6 7.0": ["concreteness"], "11.4 12.4 4.7": ["candlepower"], "4.0 11.7 1.4": ["wholesomely"], "13.3 8.3 6.9": ["romeo"], "-4.2 4.0 2.3": ["kbytes"], "1.0 8.6 10.5": ["sassier"], "-3.5 10.4 2.4": ["inrush"], "15.3 21.9 8.0": ["skulks"], "-1.2 8.0 -3.9": ["resolvers"], "4.0 14.0 7.0": ["mesothelin"], "2.6 21.6 10.4": ["slyness"], "10.7 9.8 9.3": ["lifelessness"], "11.3 3.1 8.0": ["ithe"], "4.4 8.8 9.4": ["sive"], "-2.7 1.6 1.4": ["homebased"], "4.3 14.9 39.8": ["bobwhite"], "-0.3 7.1 15.2": ["jobholders"], "14.4 13.9 0.1": ["hotwire"], "-0.3 11.1 6.8": ["clockers"], "9.2 1.7 19.6": ["sau"], "10.2 12.5 3.8": ["cames"], "4.1 25.8 2.3": ["mythologize"], "9.8 26.5 1.7": ["nefariously"], "13.8 -4.1 18.9": ["plaiting"], "14.4 14.2 3.8": ["meowed"], "9.5 12.0 28.1": ["craws"], "-7.9 3.3 5.3": ["preponed"], "16.0 6.0 6.2": ["hypergrowth"], "6.9 23.6 1.7": ["ministate"], "7.0 4.8 3.4": ["imbroglios"], "-2.9 3.1 7.2": ["ginneries"], "2.9 13.7 2.8": ["touchtone"], "-6.8 13.8 24.1": ["monga"], "-0.6 5.7 6.7": ["lasik"], "23.4 21.8 19.8": ["griffins"], "8.0 1.2 -6.3": ["wideranging"], "8.5 0.8 12.2": ["reliquaries"], "-6.8 5.7 5.5": ["hyperinsulinemia"], "-2.8 2.9 6.8": ["meconium"], "-3.8 2.2 1.5": ["tme"], "11.5 17.3 11.4": ["otherwordly"], "5.1 14.4 3.0": ["persistance"], "5.2 1.7 15.1": ["champaign"], "13.9 0.6 15.2": ["frappuccinos"], "4.8 12.4 5.3": ["pederast"], "-2.4 5.1 -1.1": ["pharmacoeconomic"], "10.1 5.1 11.9": ["overcompensates"], "-0.5 0.0 -3.9": ["transcultural"], "14.7 13.2 16.0": ["chewer"], "5.8 15.2 6.5": ["spareness"], "20.5 8.7 4.1": ["vacantly"], "13.2 7.9 1.1": ["factfile"], "11.7 -3.9 37.4": ["agnolotti"], "4.9 4.5 9.8": ["benzocaine"], "0.1 12.0 3.3": ["rurally"], "15.4 8.4 16.7": ["wiffleball"], "7.1 -1.9 3.2": ["logy"], "-6.8 14.7 1.0": ["preplan"], "18.9 4.4 10.6": ["ogles"], "5.3 15.5 4.4": ["hewers"], "4.8 8.1 13.9": ["baggier"], "18.6 19.1 9.4": ["jackbooted"], "-4.2 1.1 6.1": ["ataluren"], "-5.2 18.3 10.5": ["denuclearized"], "3.2 11.4 16.2": ["epiglottis"], "-6.8 8.7 2.7": ["sadar"], "19.8 5.3 27.4": ["liverwurst"], "5.6 9.6 9.5": ["pooched"], "-4.8 6.0 2.7": ["tolvaptan"], "15.9 13.0 14.0": ["brickbat"], "8.0 10.2 16.1": ["titbit"], "-0.8 11.7 15.1": ["cogitate"], "7.1 18.5 19.6": ["unassimilated"], "16.8 4.0 14.0": ["languorously"], "-9.0 2.0 4.6": ["oxybutynin"], "-2.2 6.8 15.6": ["hyperglycemic"], "-10.2 6.5 -3.3": ["dischargeable"], "6.2 3.0 12.4": ["roastery"], "-4.4 10.1 11.0": ["paresthesia"], "-0.1 5.3 13.1": ["purine", "aresubject"], "10.3 20.4 9.9": ["paraglide"], "6.9 5.5 6.3": ["tus"], "8.6 4.3 7.5": ["kolkata"], "3.6 9.7 0.2": ["moralization"], "11.3 6.7 18.3": ["preholiday"], "2.8 22.6 14.7": ["undertows"], "19.0 14.6 11.5": ["rockface"], "3.0 6.1 6.8": ["ethnological"], "4.7 18.9 1.4": ["beloveds"], "-1.4 15.6 4.2": ["maulvi"], "8.0 8.6 15.6": ["hacky"], "11.7 11.8 11.0": ["beatiful"], "10.4 1.3 18.9": ["breadboard"], "-4.5 2.0 13.9": ["interdistrict"], "-0.5 2.5 8.3": ["spondylitis"], "15.2 14.1 3.9": ["tenuousness"], "6.1 7.8 24.7": ["columbines"], "1.6 -3.5 8.1": ["resthome"], "9.9 16.4 8.4": ["eeriest"], "6.5 4.6 -1.7": ["twentysix"], "7.2 12.7 8.8": ["nerazzurri"], "-2.6 2.9 13.8": ["interposer"], "-0.6 6.0 12.4": ["tongas"], "8.6 8.1 16.0": ["parol"], "-5.5 14.4 5.9": ["chesed"], "11.9 10.3 0.4": ["anniversay"], "6.6 3.4 4.6": ["vos"], "18.3 11.8 14.9": ["doorless"], "5.7 17.7 8.3": ["grandstander"], "4.6 9.1 16.8": ["baat"], "-7.1 4.1 6.2": ["moneywise"], "-9.8 0.3 11.5": ["gewogs"], "7.9 13.9 37.4": ["fishless"], "7.7 8.7 3.1": ["deflowering"], "-2.2 36.0 6.5": ["hooah"], "12.9 22.5 6.8": ["thems"], "7.6 0.7 1.3": ["fillup"], "5.1 0.8 -2.4": ["footbaths"], "2.2 6.6 21.4": ["skifields"], "-1.7 9.0 12.0": ["breakevens"], "13.3 6.9 10.2": ["ify"], "4.5 7.8 6.7": ["bj"], "1.9 11.2 10.9": ["dergah"], "12.7 13.3 5.8": ["gadgety"], "7.4 3.0 10.3": ["bumpiness"], "11.1 9.5 13.9": ["upholster"], "13.3 -3.2 9.9": ["gaudiness"], "-2.5 16.3 -0.9": ["marginalises"], "9.3 12.0 -1.6": ["seing"], "11.8 7.5 15.8": ["unties"], "7.5 9.1 8.1": ["enthrals"], "6.1 3.1 7.0": ["indacaterol"], "4.0 15.3 7.6": ["bedmate"], "8.1 2.1 32.9": ["zongzi"], "1.2 9.0 3.7": ["coments"], "8.1 13.3 18.2": ["tigresses"], "-6.6 6.9 7.8": ["pseudophedrine"], "12.2 19.0 12.3": ["exhilirating"], "-9.2 15.0 6.9": ["wordiness"], "4.0 9.5 21.4": ["variegation"], "5.1 0.1 7.6": ["preprints"], "-7.8 17.5 7.5": ["burndown"], "-5.4 2.9 16.1": ["wellfields"], "15.2 4.8 8.4": ["nanosatellite"], "1.5 8.2 3.7": ["wakf"], "1.9 15.6 18.4": ["bilharzia"], "12.9 20.7 6.3": ["unobscured"], "21.0 24.3 26.9": ["kraken"], "8.1 16.7 4.3": ["noth"], "8.2 13.9 18.7": ["hahahahaha"], "14.7 12.0 5.5": ["dx"], "8.3 9.3 21.6": ["pouching"], "8.5 13.4 10.4": ["ferrari"], "10.2 14.5 33.2": ["stickbaits"], "5.0 24.1 5.9": ["uncongenial"], "6.7 2.0 31.4": ["ichthyologist"], "-3.3 14.8 7.3": ["roamer"], "-3.9 18.5 11.0": ["unchaste"], "1.0 5.1 5.7": ["intramuscularly"], "9.3 8.5 4.2": ["remolding"], "10.4 20.9 16.8": ["funguses"], "-1.9 15.3 -4.8": ["destigmatize"], "-4.2 1.2 36.1": ["grilse"], "5.9 6.4 1.0": ["embroiderer"], "10.0 2.9 3.3": ["glamming"], "2.0 0.6 3.5": ["curettage"], "-0.3 9.6 5.8": ["electrosurgery"], "2.6 6.1 12.6": ["omaha"], "1.4 3.5 2.4": ["perovskite"], "10.7 0.8 6.1": ["sweatbox"], "-1.5 12.9 18.4": ["lakeshores"], "4.0 5.3 4.0": ["keun"], "7.6 15.7 22.7": ["deadfall"], "-4.9 8.0 -0.8": ["unprogrammed"], "9.7 9.9 13.6": ["manscaping"], "11.2 7.9 24.9": ["flavourless"], "6.2 12.2 3.8": ["metatags"], "9.6 18.7 4.3": ["cauterizing"], "15.2 8.4 9.5": ["psst"], "-2.3 8.0 7.7": ["restavek"], "-10.6 2.9 -3.6": ["reprioritization"], "11.8 11.1 0.8": ["rechargers"], "-4.4 10.0 7.8": ["pneumoniae"], "-3.2 0.1 4.7": ["tahlil"], "25.3 5.5 4.7": ["superglued"], "9.7 7.9 15.4": ["earing"], "4.1 -0.4 9.8": ["fication"], "10.5 9.6 15.8": ["restring"], "-0.8 8.0 5.5": ["unrushed"], "-0.7 8.1 10.3": ["extensiveness"], "9.7 6.1 26.9": ["aquarists"], "10.3 9.9 6.3": ["latterday"], "20.2 5.7 18.5": ["dogfood"], "0.5 5.8 7.3": ["carsharing"], "4.9 8.5 4.7": ["currrent"], "11.5 12.0 20.9": ["trellised"], "7.2 9.0 19.4": ["mastication"], "12.7 26.3 15.4": ["otherworld"], "-5.4 16.0 17.7": ["commonwealths"], "-7.2 16.2 1.0": ["extemely"], "10.0 12.7 3.4": ["collimator"], "3.7 4.5 6.8": ["alors"], "8.4 2.7 29.1": ["saut"], "-5.2 8.8 8.3": ["grandsire"], "13.6 21.0 15.8": ["eejit"], "14.1 13.9 11.9": ["knuckleduster"], "4.5 2.7 7.5": ["securitizes"], "0.5 -4.6 -0.7": ["thenext"], "6.1 12.5 6.9": ["undiversified"], "10.7 15.8 19.3": ["rustler"], "12.5 9.2 15.4": ["spencer"], "13.6 9.1 16.8": ["wigwams"], "-0.7 1.8 12.0": ["proanthocyanidins"], "15.0 16.9 7.5": ["thiefs"], "-2.9 10.8 4.5": ["amplifications"], "-2.8 6.5 7.1": ["rubberstamping"], "11.8 5.0 14.4": ["earflaps"], "3.0 6.4 11.9": ["ravishingly"], "17.8 5.1 3.2": ["proft"], "2.5 1.7 11.9": ["ceramicists"], "0.2 8.9 7.1": ["sher"], "11.5 15.6 9.3": ["tailspins"], "7.4 13.0 10.0": ["canadians"], "14.8 11.4 23.2": ["speckling"], "1.6 31.2 -0.3": ["mukhabarat"], "-3.8 14.2 5.8": ["celgosivir"], "13.4 1.4 21.7": ["lilly"], "7.8 7.5 2.4": ["lable"], "-0.4 3.1 4.3": ["hangtags"], "16.5 6.4 31.4": ["humpy"], "-0.4 9.4 14.3": ["hamam"], "3.4 2.6 12.4": ["hoh"], "-6.2 4.9 0.1": ["coinfected"], "-0.5 23.0 11.5": ["embittering"], "-4.6 9.2 2.9": ["judiciousness"], "-3.6 4.8 6.3": ["antiproliferative"], "-4.0 2.0 9.5": ["sor"], "3.5 21.9 9.0": ["smokejumper"], "5.7 16.5 15.9": ["buggin"], "7.3 5.5 18.0": ["wong"], "1.1 9.2 6.5": ["chemopreventive"], "-0.8 -4.4 -1.8": ["ial"], "2.4 11.8 6.4": ["orbitals"], "15.8 16.2 18.0": ["gawker"], "-5.4 23.4 10.0": ["basestealer"], "-0.6 5.7 15.1": ["gota"], "-1.1 6.1 3.4": ["preffered"], "3.7 6.4 0.5": ["tarmacked"], "6.5 8.8 15.5": ["vocalisations"], "9.1 16.9 5.2": ["loudhailers"], "16.8 18.5 9.7": ["kaiser"], "0.7 3.3 9.6": ["datacards"], "-0.5 8.0 3.4": ["thinclads"], "10.9 8.0 8.3": ["dus"], "10.5 7.8 11.3": ["tinkled"], "15.6 9.9 9.0": ["overcaffeinated"], "23.2 1.7 13.5": ["trolly"], "5.5 6.0 24.0": ["chablis"], "0.3 9.6 2.8": ["deemphasized"], "8.7 20.6 22.0": ["nighthawks"], "11.3 -1.1 -5.9": ["fuer"], "10.8 -3.0 -3.3": ["cls"], "-1.1 7.1 -4.0": ["collateralizing"], "10.7 10.3 2.6": ["uprise"], "-7.7 3.5 0.4": ["immobilisers"], "2.4 15.6 8.7": ["baryons"], "3.1 19.6 17.7": ["puckhandling"], "11.1 10.9 16.0": ["budgeteers"], "6.0 3.8 9.7": ["resthouse"], "6.4 9.8 4.1": ["whorehouses"], "14.7 13.2 9.5": ["joyrider"], "10.7 6.9 24.5": ["lacquerware"], "6.0 11.4 1.5": ["jetsetter"], "10.7 13.8 7.0": ["weedkillers"], "5.5 20.3 6.5": ["mortify"], "-0.7 12.8 11.4": ["feminity"], "-6.6 3.6 -2.8": ["candiates"], "9.7 13.3 10.7": ["macroscale"], "5.0 -0.3 7.6": ["aerogels"], "-0.1 6.5 8.3": ["lobules"], "7.0 12.7 4.3": ["infosec"], "2.0 12.2 1.7": ["aweful"], "13.0 23.5 11.0": ["dittoheads"], "10.2 -7.2 10.4": ["constuction"], "11.0 -1.8 -0.6": ["goup"], "5.9 16.9 10.1": ["whinning"], "5.8 22.8 10.0": ["stabbers"], "3.4 7.6 3.9": ["ethers"], "10.8 19.6 7.4": ["convulses"], "0.8 12.8 28.8": ["pulao"], "4.0 2.2 5.1": ["calgary"], "9.3 4.0 10.6": ["overprivileged"], "14.7 23.3 22.1": ["smush"], "6.4 18.6 -1.0": ["desisting"], "-6.9 9.3 11.3": ["theatregoer"], "8.0 7.7 18.2": ["mislabel"], "-3.0 2.3 -1.7": ["prewired"], "9.1 4.3 20.6": ["bioaccumulation"], "12.2 14.2 -6.8": ["gamechanger"], "14.5 9.2 1.4": ["divestures"], "-7.2 0.8 8.6": ["haematological"], "9.4 15.0 18.1": ["chokeslammed"], "-6.3 12.2 7.5": ["insightfulness"], "21.1 12.0 4.4": ["arbitragers"], "12.9 8.1 7.8": ["towables"], "-1.5 9.7 -1.1": ["possessory"], "7.8 10.2 2.3": ["lineament"], "3.9 9.3 28.2": ["goldens"], "-1.4 4.8 11.6": ["kampungs"], "-2.9 11.4 9.6": ["biopesticide"], "4.8 9.9 20.2": ["dacite"], "9.6 3.4 27.5": ["goetta"], "4.4 6.4 16.4": ["cornpone"], "2.4 1.2 6.0": ["beh"], "13.4 4.5 5.0": ["enmesh"], "10.8 0.7 15.3": ["maryland"], "9.3 21.0 16.9": ["redskin"], "6.3 -3.9 7.5": ["racebook"], "0.6 8.4 3.3": ["unitization"], "-10.7 0.1 10.4": ["boldenone"], "8.6 16.7 13.0": ["pejoratives"], "19.5 12.5 13.0": ["longhairs"], "-3.4 6.0 5.2": ["irbesartan"], "0.4 23.3 -0.4": ["egocentrism"], "8.6 5.2 34.5": ["mousseline"], "11.6 6.1 12.4": ["pediments"], "5.8 24.2 17.4": ["maces"], "2.1 8.2 16.0": ["microcell"], "18.7 13.4 25.2": ["featherless"], "2.2 7.9 19.4": ["miraa"], "9.5 5.8 23.1": ["oviduct"], "-5.5 3.9 -1.1": ["batchmate"], "15.5 12.5 9.3": ["damm"], "-1.7 17.1 11.8": ["leukemic"], "-2.2 23.5 3.5": ["intercessors"], "0.0 -1.7 8.8": ["gainsharing"], "2.0 6.5 37.0": ["gumbos"], "1.4 1.6 2.6": ["showcause"], "17.1 18.3 21.6": ["breadbaskets"], "-11.2 16.3 3.7": ["wittiness"], "1.0 12.2 11.3": ["consitutional"], "7.6 16.3 5.6": ["purloin"], "5.7 16.1 2.7": ["prettify"], "6.8 12.2 11.7": ["whippin"], "4.5 13.5 16.6": ["wiseass"], "17.7 17.3 17.8": ["boogey"], "-7.4 8.3 3.7": ["outkick"], "-0.7 7.4 11.7": ["unsuitably"], "0.3 8.3 1.4": ["distention"], "0.8 8.5 13.3": ["longboarder"], "-5.1 8.3 10.4": ["nonwork"], "-6.2 2.0 -3.1": ["statments"], "-1.3 7.6 -9.1": ["sideload"], "10.7 19.6 11.4": ["moonlets"], "4.0 6.5 -0.5": ["electroencephalography"], "8.0 13.8 8.7": ["horniness"], "-2.3 8.1 15.1": ["goitre"], "7.5 4.1 20.8": ["matka"], "8.0 11.4 7.7": ["stereotypic"], "8.6 3.3 8.6": ["dns"], "8.8 15.6 21.6": ["limper"], "18.5 3.6 8.0": ["bankex"], "5.7 -0.2 15.8": ["maggie"], "4.3 1.9 -4.3": ["photokina"], "7.4 8.8 9.8": ["tenners"], "5.3 6.2 10.4": ["penchants"], "3.4 13.1 0.9": ["allegedy"], "4.9 9.7 9.2": ["embraceable"], "1.2 13.1 9.4": ["turntablists"], "-0.1 -0.6 2.2": ["midswaps"], "20.2 11.4 6.9": ["sofware"], "8.6 2.1 30.2": ["cockling"], "-0.5 24.5 3.0": ["dignifies"], "-5.3 -1.2 5.7": ["chairpeople"], "14.0 9.4 7.1": ["twitpic"], "4.5 13.5 8.4": ["solidness"], "-3.1 -0.4 -0.7": ["giu"], "8.1 36.2 18.1": ["gooks"], "1.6 17.3 6.2": ["perogative"], "8.8 36.1 15.3": ["helos"], "5.9 13.4 10.0": ["scarifying"], "8.3 7.7 35.2": ["achiote"], "-3.9 8.2 13.4": ["magiging"], "6.4 -6.2 1.8": ["ved"], "11.3 11.2 10.5": ["fluoresces"], "15.3 19.2 5.4": ["exhilarate"], "11.0 19.9 13.5": ["ladyfriend"], "5.2 16.8 1.3": ["pamphleteering"], "12.2 8.3 15.0": ["frothiness"], "14.6 11.2 1.6": ["sytems"], "5.4 13.3 -3.9": ["succesfull"], "14.2 3.2 18.3": ["betty"], "10.0 15.8 8.2": ["gearlever"], "6.9 10.2 6.9": ["homolog"], "-7.2 -2.3 2.4": ["vodcast"], "13.5 15.8 10.1": ["taikonaut"], "7.3 24.2 3.3": ["tyrannize"], "9.8 6.2 19.8": ["sienna"], "5.7 10.6 4.9": ["salving"], "4.1 8.0 1.4": ["blubbered"], "5.0 1.8 9.3": ["horseshoeing"], "12.5 6.3 22.5": ["pudge"], "-8.1 8.4 5.4": ["macrolide"], "8.2 6.5 6.9": ["maquilas"], "13.7 13.8 12.2": ["syncline"], "11.9 21.7 7.8": ["confusedly"], "-2.8 22.0 1.6": ["sunnah"], "9.5 9.5 8.2": ["accumulatively"], "14.1 13.4 23.5": ["heliotrope"], "-3.8 -1.3 -1.1": ["sevoflurane"], "20.5 20.5 10.2": ["faceplant"], "9.2 12.7 11.3": ["standin"], "-0.1 5.0 12.0": ["quadrennium"], "7.3 9.6 1.1": ["rewires"], "-0.3 9.1 1.3": ["granisetron"], "5.6 16.8 13.1": ["intellectualizing"], "-1.1 8.8 -1.0": ["heared"], "3.0 17.3 4.7": ["transhumanist"], "0.8 16.2 27.5": ["brome"], "-4.6 2.4 -1.6": ["dcp"], "-5.3 -2.5 16.4": ["restockers"], "9.6 5.0 13.8": ["pil"], "0.2 21.9 6.2": ["laicism"], "6.5 7.6 11.9": ["superspecial"], "5.0 4.4 6.8": ["renounceable"], "-0.7 -2.4 -4.2": ["nonpaid"], "-5.0 1.1 1.1": ["salicylate"], "11.9 8.6 -1.0": ["worl"], "7.0 19.1 26.3": ["reefed"], "1.7 1.8 -0.8": ["quitclaim"], "14.4 10.0 14.8": ["crapload"], "6.8 2.6 7.2": ["zanier"], "11.2 18.6 23.3": ["blowholes"], "10.0 6.6 23.8": ["schnitzels"], "0.8 3.2 4.5": ["fullfill"], "9.3 16.9 23.1": ["bowstring"], "8.7 1.9 12.9": ["murphy"], "-2.4 6.3 12.7": ["gaging"], "14.4 12.1 21.0": ["chinking"], "3.0 14.5 15.2": ["shiksa"], "2.5 1.1 10.7": ["cre"], "-5.5 2.4 0.8": ["revaluated"], "8.3 5.3 6.4": ["unsent"], "3.3 8.5 2.5": ["millivolts"], "17.1 14.1 11.0": ["pictograph"], "-1.1 -1.2 9.2": ["caudate"], "0.2 21.6 7.5": ["obstinance"], "17.8 10.1 10.2": ["transmogrify"], "6.0 -0.8 1.9": ["preleased"], "-3.0 17.2 11.9": ["heterosexist"], "10.6 15.2 4.3": ["reflagged"], "8.9 20.9 6.6": ["cagy"], "4.4 14.8 13.2": ["karoshi"], "2.2 -2.8 8.6": ["permanents"], "-10.8 17.2 2.3": ["empiric"], "-3.8 6.0 9.7": ["charrettes"], "10.6 5.3 5.3": ["inflators"], "3.8 2.2 2.1": ["dancehalls"], "24.7 7.2 7.4": ["buttonless"], "12.0 9.1 29.0": ["fiords"], "9.7 2.6 13.9": ["mantelpieces"], "12.4 6.2 13.0": ["headstands"], "7.6 4.6 14.9": ["kneeler"], "11.6 13.5 0.3": ["updateable"], "16.4 12.4 16.0": ["artifically", "sweary"], "-2.2 14.6 5.7": ["unordinary"], "1.4 10.1 10.5": ["monocyte"], "-0.6 2.3 12.3": ["shirtdresses"], "4.0 1.0 10.3": ["chanel"], "11.0 15.4 10.7": ["withal"], "-2.2 5.5 4.5": ["pheochromocytoma"], "-0.4 9.0 0.4": ["camptothecin"], "-0.5 7.2 11.4": ["gossans"], "12.6 30.3 4.5": ["fusillades"], "11.5 33.8 4.8": ["malefactor"], "13.0 15.0 11.8": ["lodestone"], "11.2 7.6 36.6": ["pipefish"], "0.7 2.5 16.2": ["fibia"], "3.3 2.5 13.3": ["syllabic"], "4.5 6.7 -3.3": ["affaire"], "-4.8 9.2 5.6": ["vasospasm"], "0.0 24.3 10.4": ["sovereignity"], "10.3 2.5 13.5": ["mur"], "8.3 12.4 9.2": ["bluray"], "6.3 6.8 10.3": ["strongbox"], "-4.4 6.7 20.0": ["enteritis"], "0.3 0.7 6.1": ["kd"], "13.5 8.2 14.8": ["greybeard"], "7.2 8.4 12.9": ["olympian"], "12.2 17.8 9.4": ["miserliness"], "17.9 6.8 13.7": ["dementedly"], "3.4 12.9 8.4": ["neigborhood"], "0.1 2.3 14.4": ["chambray"], "-1.9 9.9 6.6": ["thromboxane"], "-2.6 5.2 10.5": ["jughandle"], "-6.8 -6.7 -3.2": ["awared"], "8.5 8.7 9.6": ["vick"], "3.3 22.5 4.2": ["foreswear"], "9.6 7.2 22.5": ["lanais"], "2.3 9.8 23.6": ["kuru"], "-9.5 1.5 2.3": ["attender"], "11.4 9.5 15.1": ["caner"], "10.4 0.5 12.2": ["seatholders"], "22.7 10.1 14.8": ["sawhorse"], "-4.9 12.4 5.7": ["ascorbate"], "4.1 13.9 11.4": ["misreport"], "4.7 4.8 8.9": ["degrowth"], "-4.6 6.2 10.9": ["swaras"], "-2.6 9.9 10.0": ["disbelieves"], "7.9 10.5 4.4": ["dismemberments"], "6.0 6.7 2.6": ["hommage"], "-2.3 12.1 12.3": ["photoaging"], "6.0 10.2 3.2": ["triband"], "1.9 6.3 7.3": ["songsmiths"], "1.3 12.2 4.7": ["codeshares"], "-3.9 7.2 -2.0": ["individualise"], "8.1 5.0 15.4": ["albuquerque"], "3.0 15.9 7.6": ["perihelion"], "4.7 16.5 19.4": ["crampon"], "2.2 24.9 11.9": ["unobservant"], "7.6 0.7 8.0": ["housepainter"], "8.0 10.5 4.6": ["huffily"], "8.9 12.7 8.9": ["wittering"], "6.2 12.7 11.4": ["slapsticky"], "6.0 13.3 11.0": ["illseed"], "9.4 0.1 16.1": ["thickset"], "3.7 1.6 16.6": ["chou"], "-0.0 7.5 9.1": ["subzone"], "11.7 12.8 10.4": ["flatlines"], "12.1 9.2 33.5": ["moulting"], "2.3 2.4 6.8": ["conjunctival"], "8.1 28.2 20.8": ["forecheckers"], "-5.4 10.0 2.6": ["responce"], "23.7 5.3 8.9": ["drugmaking"], "10.7 2.0 20.2": ["highboy"], "-1.4 12.2 -0.2": ["computable"], "13.8 8.6 6.5": ["contently"], "8.6 3.2 5.1": ["rankest"], "8.3 11.7 27.8": ["epicure"], "6.6 3.6 10.9": ["donc"], "5.2 1.3 6.5": ["thermostatic"], "-3.3 -0.2 9.0": ["daybook"], "14.7 17.5 6.6": ["gatepost"], "4.4 1.8 8.2": ["datapoints"], "-2.0 1.7 14.2": ["martinez"], "7.6 8.3 7.1": ["chasis"], "16.9 16.0 13.7": ["ownerless"], "4.0 13.6 5.6": ["saliency"], "6.7 7.9 8.9": ["itu"], "4.5 10.2 2.3": ["aerodynamicist"], "2.1 23.9 13.0": ["uncased"], "13.6 3.4 -1.9": ["standardises"], "0.4 22.0 10.1": ["beatitude"], "-4.6 6.9 1.2": ["plasmapheresis"], "5.1 -1.0 6.4": ["quien"], "0.1 9.0 17.2": ["cong"], "15.8 21.1 26.3": ["kea"], "12.3 12.8 5.0": ["resizes"], "13.9 14.2 15.8": ["gloomers"], "1.6 23.3 1.5": ["beind"], "7.5 20.0 6.8": ["presumptuousness"], "-8.0 2.5 5.8": ["excisions"], "-6.9 13.7 9.3": ["disfranchisement"], "-3.6 2.4 13.3": ["balikbayans"], "3.5 10.6 11.1": ["unfocussed"], "3.3 17.8 8.7": ["pantheistic"], "13.3 22.8 30.3": ["stinkbugs"], "21.9 15.4 6.8": ["fanbois"], "9.6 15.2 47.5": ["spadefish"], "10.7 13.5 0.3": ["barnstormers"], "-0.3 15.6 12.4": ["partymates"], "-5.9 7.9 5.6": ["hyperglycaemia"], "-1.6 3.9 6.5": ["tithed"], "5.4 7.5 -5.3": ["outlicense"], "17.6 16.7 4.1": ["firestarter"], "-1.6 5.6 16.4": ["peacoats"], "0.5 16.6 9.9": ["brilliancy"], "1.6 14.2 9.8": ["shelterbelts"], "-3.2 9.6 3.9": ["relitigating"], "10.9 -4.1 5.7": ["uhl"], "5.1 15.4 9.4": ["ribosomal"], "4.5 13.6 5.9": ["omacetaxine"], "-2.3 -0.8 10.1": ["horsepeople"], "9.9 12.6 5.2": ["raptly"], "8.9 20.8 9.9": ["unutterable"], "-1.4 7.5 17.6": ["silkiness"], "-4.5 13.3 0.8": ["nanoviricides"], "0.6 -2.6 4.2": ["overaged"], "14.4 6.2 12.1": ["sleepiest"], "3.9 7.3 8.0": ["buddhist"], "21.8 6.5 5.3": ["moneyspinner"], "7.3 9.0 3.2": ["interferometric"], "7.5 4.8 15.9": ["overeaters"], "2.1 14.8 5.5": ["abrasively"], "9.3 16.1 10.6": ["photocell"], "5.6 2.9 3.4": ["descibed"], "2.5 2.1 25.9": ["tangelos"], "4.4 2.1 9.4": ["divertissement"], "12.0 5.9 4.2": ["skeezy"], "21.0 13.3 3.0": ["billons"], "6.1 6.7 26.5": ["shipwrights"], "3.4 6.7 10.5": ["screamy"], "-0.6 2.9 9.1": ["baud"], "10.4 14.9 7.0": ["unimportance"], "19.5 30.8 21.5": ["torpedos"], "5.7 9.3 -3.8": ["microcircuits"], "7.4 12.1 17.9": ["brays"], "8.4 19.4 6.4": ["explorable"], "5.9 19.6 5.0": ["discriminators"], "3.1 5.3 7.9": ["passagework"], "8.9 9.9 11.3": ["aholics"], "0.2 4.6 6.6": ["ozonation"], "9.4 7.7 6.9": ["polution"], "3.0 15.3 32.0": ["kaiseki"], "8.7 7.4 5.1": ["underpays", "thst"], "7.1 16.4 19.6": ["yapper"], "11.9 28.2 9.2": ["arial"], "6.4 8.8 9.7": ["vaastu"], "5.1 3.0 12.1": ["hydros"], "-1.9 3.1 2.3": ["betrixaban"], "8.1 5.4 18.3": ["blousy"], "5.0 -8.8 0.7": ["includ"], "8.6 7.7 12.1": ["celebrator"], "1.9 5.5 -0.1": ["safinamide"], "1.8 0.8 -0.4": ["invloved"], "8.3 23.2 12.0": ["deflationists"], "6.2 6.3 7.6": ["numero"], "-2.1 0.2 6.2": ["scenically"], "8.2 21.9 9.3": ["boomeranging"], "9.5 13.6 17.0": ["creampuff"], "-3.0 -4.0 6.7": ["twoday"], "4.2 11.8 4.4": ["overated"], "-4.0 6.9 18.0": ["unoaked"], "2.4 11.1 12.3": ["candids"], "10.6 13.7 16.2": ["doberman"], "16.2 7.5 15.8": ["insouciantly"], "-1.8 10.2 6.5": ["parathyroid"], "9.6 16.5 15.1": ["sinuously"], "8.4 7.0 15.0": ["jy"], "-6.0 -0.3 -4.9": ["ional"], "-1.5 5.7 6.8": ["corrido"], "1.6 13.6 4.6": ["abridges"], "3.4 21.9 11.4": ["ostracising"], "-9.1 4.3 19.0": ["shorezone"], "2.8 4.7 10.9": ["thera"], "5.9 9.0 2.4": ["rationalises"], "11.1 5.2 26.8": ["kirsch"], "10.0 15.5 10.3": ["throwed"], "6.2 19.0 20.2": ["whelp"], "11.3 0.2 25.3": ["bulkers"], "1.1 -0.2 3.5": ["microporous"], "2.4 9.2 14.4": ["phytoremediation"], "-4.2 16.6 4.2": ["mindframe"], "-6.6 2.5 4.4": ["airdates"], "12.8 20.6 9.3": ["warmists"], "2.3 25.9 6.0": ["unheroic"], "0.0 3.1 5.0": ["carbureted"], "-3.6 13.9 -2.5": ["discipling"], "-5.3 13.7 6.2": ["espeically"], "-5.9 6.4 10.5": ["ough"], "4.3 0.4 6.7": ["promissory"], "1.1 5.7 5.1": ["parsers"], "6.7 3.1 12.8": ["acrossthe"], "-3.3 1.5 6.1": ["bondable"], "9.3 18.9 10.7": ["senescent"], "6.5 -0.9 -2.1": ["stationeries"], "-3.8 3.8 6.6": ["supp"], "-1.5 2.7 5.9": ["topnotcher"], "5.0 9.7 49.2": ["cohos"], "11.2 8.6 2.8": ["agreat"], "-4.9 0.2 2.4": ["licentiate"], "3.9 13.9 1.7": ["reflectiveness"], "17.4 -0.5 12.0": ["spackled"], "3.5 2.4 7.1": ["engorgement"], "2.0 7.5 4.0": ["plagiarise"], "8.5 3.3 35.7": ["caprese"], "6.1 6.4 5.1": ["preperations"], "-4.8 15.3 1.7": ["recruting"], "12.0 26.8 10.9": ["unorthodoxy"], "5.7 3.6 10.8": ["rmb"], "-2.5 8.0 11.2": ["mataqali"], "11.5 -5.8 -2.7": ["millionin"], "-13.2 10.7 -0.1": ["dipropionate"], "7.1 9.2 20.0": ["sawyer"], "12.3 24.5 14.2": ["medievalism"], "6.3 0.4 10.1": ["swimathon"], "13.0 3.5 7.8": ["stratospherically"], "15.5 4.9 10.2": ["aol"], "8.1 26.5 -0.7": ["thugocracy"], "22.3 12.4 16.3": ["mincer"], "3.7 10.5 8.9": ["notchy"], "4.7 16.0 8.3": ["garroted"], "15.5 11.6 4.9": ["fortresslike"], "6.4 12.2 15.1": ["rihanna"], "20.1 15.9 13.5": ["scaffoldings"], "14.8 11.5 4.6": ["stereoscope"], "0.9 -5.2 10.4": ["shawn"], "-3.6 3.8 5.4": ["compendia"], "9.3 1.2 46.2": ["marron"], "6.7 3.2 5.9": ["luxuriousness"], "14.1 6.6 9.5": ["delists"], "-4.7 10.5 10.1": ["untenured"], "5.6 7.2 11.7": ["gree"], "-2.0 12.7 5.8": ["matricide"], "1.9 3.5 11.8": ["arnica"], "0.1 18.4 -0.9": ["egoless"], "12.0 4.4 9.3": ["tainment"], "2.7 12.6 19.1": ["exfoliator"], "12.7 2.7 7.2": ["residental"], "7.5 6.3 0.4": ["offcial"], "5.4 8.0 3.6": ["defragging"], "4.3 10.2 2.9": ["intermountain"], "-0.1 10.1 12.0": ["recomposed"], "8.1 6.4 11.7": ["neuroeconomics"], "4.0 10.5 9.9": ["unclutter"], "9.9 17.3 12.6": ["oneupmanship"], "12.6 16.1 10.0": ["tenderfoot"], "4.9 15.9 6.4": ["bootlicking"], "-6.2 4.9 5.3": ["rerecord"], "0.3 18.6 7.4": ["sardars"], "9.8 2.9 9.9": ["spliffs"], "-1.0 11.7 10.0": ["drillbit"], "14.5 2.9 26.3": ["fondues"], "-6.5 1.5 0.1": ["decrements"], "15.4 17.6 9.0": ["apathetically"], "-5.1 13.1 18.6": ["kari"], "1.3 14.5 9.4": ["calcineurin"], "-1.4 1.7 -2.6": ["endorsees"], "3.7 25.6 6.0": ["consquences"], "9.6 26.7 -0.0": ["chasten"], "5.0 -4.2 14.3": ["ket"], "10.9 4.4 20.9": ["duchesses"], "-2.2 6.2 11.8": ["unremarkably"], "5.1 13.4 18.0": ["mali"], "5.7 3.1 21.1": ["whare"], "-0.4 1.8 15.2": ["farebox"], "21.5 6.6 16.2": ["manky"], "2.6 16.0 5.3": ["legitmate"], "-1.6 16.6 16.3": ["recreationalists"], "-8.0 6.4 15.8": ["sewering"], "15.4 15.8 17.2": ["anima"], "1.4 4.6 -0.2": ["goa"], "3.2 16.1 13.6": ["moony"], "10.5 1.7 -1.0": ["intergration"], "11.1 21.0 3.6": ["bungler"], "1.3 6.1 6.4": ["kenya"], "-0.9 9.4 12.2": ["ened"], "-7.5 12.9 9.0": ["roaders"], "14.9 -0.9 13.3": ["oxo"], "1.2 3.2 -5.3": ["audiocassette"], "7.0 14.4 15.6": ["burs"], "4.6 6.6 13.7": ["vignerons"], "-5.2 12.6 4.9": ["inwhich"], "-4.2 10.0 15.4": ["chlorothalonil"], "2.7 1.4 18.0": ["tua"], "-10.9 0.0 12.8": ["craniosynostosis"], "1.5 15.7 17.1": ["nawabs"], "13.2 -0.2 5.5": ["fluidics"], "6.0 1.8 10.4": ["strummer"], "10.8 6.9 33.3": ["gelee"], "-1.0 16.7 -3.7": ["fueler"], "1.1 -3.6 26.0": ["degustation"], "-5.6 6.5 0.9": ["enfranchising"], "4.1 -1.3 3.9": ["jobcentres"], "-2.8 -8.9 6.3": ["schoo"], "5.8 11.7 34.7": ["redds"], "1.9 12.0 2.2": ["carefull"], "11.0 -3.6 11.4": ["kalimba"], "0.4 13.0 27.9": ["flowage"], "-4.7 1.9 16.2": ["ovulated"], "3.0 24.1 5.9": ["majoritarianism"], "1.6 3.9 2.3": ["momlogic"], "4.6 -2.9 -3.2": ["cour"], "7.8 14.4 16.9": ["phloem"], "8.9 12.1 4.1": ["waterjets"], "2.3 23.8 1.5": ["calculatingly"], "3.3 29.6 6.0": ["depersonalize"], "5.4 10.7 4.3": ["probly"], "1.2 13.0 1.2": ["reacquainting"], "-10.4 10.1 10.3": ["halachah"], "-2.0 8.1 8.1": ["kriti"], "0.9 1.1 14.3": ["undercrossing"], "5.9 0.2 5.8": ["flv"], "7.1 6.4 3.2": ["lendings"], "9.7 8.6 5.2": ["inspirationally"], "-1.3 5.7 1.2": ["phacoemulsification"], "-0.3 7.9 -3.5": ["qouted"], "6.5 14.1 10.2": ["bantustans"], "10.2 11.4 5.4": ["biosynthetic"], "9.7 6.3 5.7": ["whichis"], "15.2 10.6 30.9": ["refried"], "-8.1 20.0 17.1": ["rido"], "8.6 8.2 2.9": ["px"], "3.4 2.7 6.1": ["kow"], "6.1 6.4 1.5": ["milliard"], "9.7 9.8 13.3": ["euthanise"], "3.3 13.9 11.8": ["chapping"], "5.7 10.5 15.4": ["teratomas"], "0.6 8.0 13.9": ["phytonutrient"], "9.8 6.9 15.0": ["chicha"], "5.3 4.9 2.1": ["phenotyping"], "1.5 16.2 10.7": ["idealizes"], "0.8 21.9 7.2": ["playtest"], "11.7 10.1 16.4": ["dreamin"], "1.7 11.4 6.1": ["untypically"], "3.9 15.9 10.3": ["preventatives"], "4.0 4.9 4.7": ["geosynthetics"], "4.1 14.3 4.2": ["peroxides"], "-6.7 5.6 4.0": ["telx"], "14.8 10.3 14.9": ["snowplough"], "6.0 2.9 12.6": ["ucla"], "-0.8 1.9 23.9": ["patinas"], "4.1 9.7 7.8": ["prot"], "7.0 29.3 10.7": ["manoeuvr"], "11.7 5.5 27.9": ["sandhill"], "8.5 -4.8 7.4": ["dalla"], "-2.6 17.8 6.3": ["inwardness"], "3.0 13.9 8.1": ["formability"], "-4.6 1.7 9.8": ["euribor"], "2.2 20.3 8.5": ["personifications"], "2.5 3.5 12.8": ["lawrence"], "9.3 -1.1 10.4": ["kneelers"], "17.8 2.4 4.6": ["videoboards"], "1.7 -5.3 4.3": ["terajoules"], "20.0 0.8 17.0": ["lucite"], "5.6 -1.6 -6.4": ["digitalizing"], "12.7 25.0 10.1": ["russians"], "12.3 1.2 41.8": ["bocaccio"], "-4.9 1.7 12.7": ["backload"], "9.5 7.6 16.9": ["faunal"], "19.7 9.1 16.3": ["mankini"], "-2.5 8.8 12.0": ["ehh"], "3.1 11.9 19.2": ["hap"], "4.1 15.9 4.6": ["bcc"], "4.7 7.7 -0.9": ["itzbig"], "8.1 19.3 6.9": ["perceptually"], "10.6 8.2 13.5": ["ladette"], "21.2 4.1 2.1": ["assurer"], "8.2 5.2 9.4": ["parkette"], "-7.8 -1.4 2.8": ["retainership"], "12.3 -3.8 5.2": ["wholesaled"], "4.5 7.3 22.7": ["heathers"], "-4.8 7.5 14.0": ["consecrations"], "1.4 3.5 13.0": ["churidar"], "5.1 19.7 15.2": ["pov"], "7.0 -1.2 6.1": ["nxt"], "14.9 -4.8 14.7": ["biodigester"], "1.3 1.3 7.3": ["baggages"], "-1.5 16.7 5.8": ["meritoriously"], "-1.0 7.2 8.6": ["misspend"], "1.1 5.5 8.8": ["seong"], "12.0 2.1 8.1": ["pumpin"], "14.1 15.3 11.4": ["kowtows"], "-1.6 4.5 6.7": ["sterilisations"], "4.9 -1.8 31.5": ["jamon"], "21.3 7.1 30.5": ["arepa"], "3.4 11.2 1.0": ["hypothecation"], "-6.3 -4.5 -3.4": ["tutorship"], "-0.5 12.2 8.9": ["enteroviruses"], "12.4 14.6 5.5": ["impenetrably"], "-2.1 4.8 1.2": ["conwert"], "7.1 7.4 13.8": ["concretes"], "-8.0 6.7 2.6": ["tightenings"], "9.5 10.8 28.5": ["waxwings"], "4.9 10.6 4.9": ["weeked"], "-1.1 -2.8 3.2": ["smallbusiness"], "6.8 1.7 5.8": ["cambio"], "13.4 9.5 13.6": ["slowpokes"], "-3.6 16.1 12.5": ["hametz"], "0.8 14.9 -1.5": ["unstinted"], "2.2 5.6 8.6": ["stylesheets"], "7.6 0.9 8.2": ["plaints"], "11.0 20.4 7.6": ["ultraviolence"], "4.8 2.9 38.1": ["fettucine"], "12.8 7.3 27.1": ["tagines"], "6.0 29.9 4.9": ["overawe"], "1.0 -2.0 2.2": ["nanofiltration"], "5.9 3.0 11.2": ["glaciations"], "15.0 18.2 2.8": ["transformable"], "-2.2 19.3 20.5": ["boatspeed"], "9.3 12.1 21.2": ["lulav"], "-2.9 -3.9 9.7": ["reinspections"], "8.0 10.5 2.5": ["leftwards"], "10.5 17.2 4.4": ["fiefs"], "2.1 21.7 18.3": ["kidder"], "14.8 10.6 30.5": ["lorikeets"], "8.1 15.1 8.2": ["eugenicist"], "17.3 17.2 8.7": ["somesuch"], "9.6 7.4 4.0": ["untransparent"], "8.8 -1.7 2.1": ["resubmits"], "3.0 6.3 11.1": ["thiol"], "9.7 7.7 9.5": ["anonymization"], "1.2 2.2 0.2": ["electrocardiographic"], "-4.1 16.4 3.4": ["swayamsevaks"], "-6.4 3.3 -3.0": ["firstteam"], "5.6 9.7 9.3": ["noncustomers", "cablecard"], "3.4 12.5 16.4": ["foreshock"], "5.8 4.0 0.9": ["prominant"], "-1.5 -3.1 12.0": ["bona"], "-2.5 8.7 4.3": ["eparchies"], "13.4 11.3 20.7": ["heatproof"], "11.2 11.4 11.2": ["kop"], "-11.2 4.2 8.5": ["glycemia"], "1.7 2.0 -0.5": ["gy"], "5.2 9.2 3.6": ["bulleting"], "-1.2 3.9 11.0": ["desilted"], "7.7 9.6 30.9": ["troller"], "3.8 3.4 23.0": ["restos"], "21.5 15.7 13.2": ["spiderwebs"], "10.6 1.4 3.2": ["reinject"], "5.1 6.9 5.6": ["vb"], "0.0 15.7 -3.4": ["aircrash"], "2.5 13.0 5.5": ["opaquely"], "6.3 5.8 1.1": ["typographer"], "-0.9 5.9 8.1": ["alkanes"], "-3.8 13.2 10.7": ["waragi"], "5.1 0.6 10.1": ["quarterhorses"], "-0.3 16.1 14.2": ["incommensurate"], "10.4 13.2 17.1": ["buddleia"], "-1.9 13.4 6.5": ["appurtenant"], "4.8 24.3 4.6": ["profoundest"], "-0.5 14.6 9.1": ["filtrate"], "9.8 22.3 9.7": ["elusively"], "4.8 10.9 7.9": ["pyrethrin"], "2.7 5.1 14.0": ["devi"], "-0.5 7.5 5.1": ["adecatumumab"], "8.6 1.6 -1.5": ["eneloop"], "5.6 5.5 9.8": ["rive"], "10.8 1.0 22.1": ["chalupas"], "19.3 5.4 12.5": ["brickie"], "8.8 -4.4 5.1": ["shortform"], "4.5 14.1 15.0": ["firepits"], "14.9 5.5 0.6": ["noncorporate"], "7.8 4.3 34.2": ["crudites"], "16.2 5.2 16.5": ["retched"], "1.7 4.6 30.6": ["margherita"], "6.8 8.1 4.6": ["pentru"], "19.2 7.5 16.2": ["weathervanes"], "4.8 13.5 13.4": ["skyk", "pauperization"], "9.0 14.9 33.0": ["weedbeds"], "-6.5 5.8 4.1": ["violists"], "22.5 14.2 11.2": ["showoffs"], "0.2 20.4 9.1": ["handspeed"], "3.9 5.5 10.1": ["overbidding"], "16.5 8.7 13.9": ["whatnots"], "-10.9 -2.3 2.0": ["optomistic"], "0.4 7.9 10.7": ["lampard", "wordage"], "17.0 15.2 9.6": ["parching"], "3.9 -1.3 15.2": ["spinel"], "-4.3 -0.2 7.3": ["readopted"], "1.6 -8.9 -6.5": ["prestigeous"], "-2.6 16.8 2.5": ["sprinklered"], "14.7 16.3 6.7": ["gougers"], "1.6 7.0 6.0": ["cerrado"], "-1.0 9.0 8.4": ["lenght"], "-1.6 16.0 12.3": ["disorderliness"], "12.0 6.5 11.7": ["glossiness"], "1.8 0.5 38.1": ["ribeyes"], "4.9 15.9 3.9": ["mispronounces"], "9.2 10.0 14.5": ["eminem"], "14.2 20.5 9.2": ["ninepins"], "17.1 12.5 2.7": ["skunkworks"], "2.1 5.1 6.0": ["hott"], "1.4 12.1 9.5": ["canings"], "1.5 4.0 12.4": ["komiks"], "8.7 4.2 7.2": ["quadrangles"], "11.1 11.2 11.1": ["nooooo"], "-6.9 3.7 11.0": ["remarriages"], "-7.1 4.6 4.1": ["ropinirole"], "1.5 14.1 9.2": ["emetic"], "1.6 -3.1 2.7": ["fumarate"], "2.4 -1.9 3.3": ["garnisheed"], "-3.9 33.0 -0.4": ["aggress"], "6.3 8.8 0.7": ["blatent"], "6.3 -0.6 -8.1": ["syngo"], "5.1 7.9 8.4": ["ghana"], "-1.3 5.7 15.9": ["subtopics"], "13.6 5.8 10.0": ["enourmous"], "2.2 22.8 6.5": ["athiest"], "20.6 3.9 21.5": ["ewer"], "-0.8 1.5 6.9": ["thermoregulation"], "-0.4 -4.3 -8.1": ["thedevelopment"], "1.3 5.5 9.2": ["aba"], "0.6 3.1 8.9": ["difficile"], "16.0 7.0 10.5": ["dicky"], "6.1 -0.1 42.7": ["saltfish"], "14.6 28.2 11.0": ["corrupters"], "10.2 10.5 10.7": ["mudguard"], "7.3 3.8 11.6": ["primadonna", "garnett"], "10.0 4.2 14.3": ["glommed"], "6.1 6.4 -1.0": ["firt"], "4.5 4.3 6.5": ["mlm"], "-3.2 -3.1 9.4": ["preretirement"], "6.1 -3.1 2.7": ["abour"], "0.6 -1.5 3.3": ["cannulas"], "12.4 8.9 16.6": ["crones"], "9.0 18.0 21.6": ["quadrupeds"], "8.9 3.2 11.7": ["yakker"], "-6.3 7.5 8.4": ["astrocytoma"], "3.1 3.4 13.2": ["vallenato"], "1.7 9.5 6.2": ["donums"], "23.3 8.6 19.6": ["windsocks"], "-9.0 2.8 8.7": ["assits"], "5.5 7.5 4.4": ["bmw"], "9.0 10.1 0.7": ["writeable"], "-1.0 13.6 10.7": ["defoe"], "6.7 -4.7 6.9": ["bariatrics"], "0.7 14.9 10.8": ["neurochemicals"], "2.5 -0.9 15.1": ["weigher"], "24.3 9.0 32.5": ["tubeworms"], "5.1 26.7 3.0": ["pyromaniacs"], "1.6 13.4 9.3": ["shelfware"], "7.0 1.8 2.1": ["speediness"], "23.5 11.8 9.5": ["teleco"], "11.6 8.1 13.9": ["littlies"], "2.0 -1.0 6.1": ["eto"], "-2.2 10.3 11.0": ["twinbills"], "6.1 7.4 7.5": ["almirahs"], "6.8 11.2 13.5": ["frivolousness"], "13.2 -7.3 12.8": ["gussying"], "10.0 6.4 20.1": ["gramma"], "14.6 12.4 13.7": ["anthropoid"], "3.3 9.5 25.0": ["lao"], "5.1 3.0 4.4": ["mois"], "9.9 9.5 18.4": ["cedarwood"], "18.7 3.2 9.2": ["limbers"], "3.9 6.4 5.6": ["waaaaaay"], "18.8 3.7 16.1": ["glockenspiels"], "8.2 7.5 7.0": ["dandified"], "24.4 9.4 11.6": ["skyscape"], "7.0 4.8 17.8": ["abra"], "-2.1 1.4 9.4": ["enologist"], "14.2 7.9 18.2": ["impalas"], "4.1 15.6 11.3": ["rythym"], "-2.5 3.2 -3.4": ["sojourned"], "4.3 19.0 2.7": ["bangladesh"], "1.6 -2.9 3.4": ["theend"], "16.3 13.5 9.7": ["gracelessly"], "-3.2 3.6 11.6": ["rais"], "3.4 7.7 4.8": ["sants"], "18.0 8.6 11.0": ["jangles"], "4.2 4.8 9.3": ["scatology"], "2.0 6.9 37.4": ["ikan"], "15.6 8.8 11.8": ["facetime"], "8.9 0.1 32.8": ["cavatelli"], "5.7 7.0 16.9": ["riddims"], "2.6 6.3 0.4": ["disabusing"], "6.4 2.0 2.5": ["whatevs"], "11.7 9.8 9.8": ["barometric"], "-2.2 22.0 6.2": ["affraid"], "-0.4 15.4 9.8": ["oversigning"], "-2.5 14.5 7.6": ["knw"], "-1.3 11.9 3.8": ["paddlings"], "3.1 1.7 -3.3": ["notarised"], "-1.0 13.3 4.8": ["meditator"], "-6.7 8.5 2.2": ["enfuvirtide"], "-3.4 12.9 12.9": ["ridging"], "-1.0 20.7 0.3": ["leftwinger"], "13.0 11.7 12.0": ["staved"], "10.6 11.5 6.3": ["longlasting"], "5.9 4.5 5.1": ["enterpreneurs"], "-0.9 6.0 4.7": ["mirvine"], "-5.0 -2.3 18.6": ["biosolid"], "11.0 14.1 24.3": ["inflorescence"], "-4.5 5.8 6.8": ["famil"], "-1.1 9.8 10.0": ["imperatively"], "10.1 14.5 8.9": ["complaisant"], "13.1 20.2 11.2": ["statelets"], "14.0 2.1 21.2": ["smellier"], "1.2 3.1 2.0": ["samaj"], "7.9 15.4 11.5": ["autoresponders"], "-4.5 8.2 4.0": ["stenographic"], "2.6 13.9 7.1": ["vanishingly"], "2.3 5.0 10.9": ["lk"], "2.8 11.1 9.6": ["tapori", "burton"], "-0.9 5.3 7.9": ["plenaries"], "6.0 8.6 10.6": ["imma"], "15.5 7.7 18.3": ["cenote"], "3.5 7.1 13.2": ["tokes"], "3.5 18.6 5.9": ["shia"], "14.8 -0.7 8.5": ["jetset"], "0.2 16.5 18.9": ["embayment"], "4.9 19.0 21.0": ["brumbies"], "7.2 25.5 10.2": ["telepath"], "9.9 7.4 16.7": ["biodegrading"], "2.4 4.8 6.7": ["toujours"], "2.9 11.7 31.2": ["shallop"], "5.2 21.1 9.3": ["hatefully"], "-1.7 1.6 -0.0": ["glargine"], "2.3 1.5 11.0": ["kyphosis"], "7.6 12.9 8.8": ["pyroclastic"], "2.6 4.5 11.3": ["feedwater"], "-2.5 -4.2 1.8": ["liprotamase"], "7.1 13.2 8.9": ["effluence"], "11.5 10.8 31.3": ["cowbird"], "3.7 0.4 3.7": ["fpr"], "10.9 9.9 15.3": ["mires"], "6.1 5.9 22.8": ["shorthaired"], "2.0 19.9 5.6": ["unsurmountable"], "14.2 21.8 14.9": ["earhole"], "8.8 4.0 8.9": ["devt"], "8.3 20.6 3.2": ["cryptologist"], "0.8 5.3 11.2": ["intermunicipal"], "3.4 7.7 10.0": ["rv"], "21.3 10.0 12.9": ["phobe"], "2.7 6.5 2.9": ["unintrusive"], "2.4 12.2 16.3": ["reproductively"], "19.2 18.7 7.4": ["luddites"], "-0.5 -9.2 -1.4": ["cio"], "5.8 1.8 24.4": ["pata"], "17.6 17.0 18.8": ["protoplasm"], "0.4 12.6 10.6": ["terpenes"], "-8.2 -1.0 24.1": ["haylage"], "14.2 5.4 10.2": ["drywalling"], "-0.1 3.8 9.7": ["sealings"], "-1.5 13.8 4.2": ["gratifies"], "5.6 8.8 25.5": ["unfertilized"], "18.3 17.6 10.1": ["whammo"], "-1.2 10.8 10.2": ["teratoma"], "17.5 16.5 19.9": ["squashy"], "1.1 -1.0 13.6": ["milongas"], "-1.8 11.7 4.2": ["novelizations"], "-8.4 2.8 4.5": ["drawal"], "-9.6 13.0 -5.2": ["ameer"], "-1.8 7.7 25.1": ["pawpaws"], "2.1 3.2 11.9": ["nunneries"], "19.1 5.7 12.0": ["smattered"], "6.5 0.4 19.8": ["erica"], "-5.4 4.5 -3.2": ["proximately"], "20.6 16.9 13.7": ["stylee"], "4.4 9.9 6.0": ["kep"], "9.8 1.7 1.5": ["stodginess"], "11.5 21.5 12.4": ["theif"], "10.7 8.1 21.0": ["stockbuild"], "8.1 -7.9 7.6": ["biophotonics"], "18.6 16.2 20.3": ["plink"], "14.8 8.0 9.5": ["firetrap"], "-8.8 9.5 11.4": ["rewarming"], "14.9 8.4 26.1": ["saki"], "-1.8 5.8 5.1": ["constructionist"], "2.6 26.4 1.8": ["deterrant"], "16.5 10.5 18.1": ["tikes"], "11.8 12.4 4.8": ["orphaning"], "-0.1 12.2 5.9": ["sideband"], "11.7 2.0 51.3": ["quahog"], "0.8 2.8 31.5": ["nasi"], "9.4 12.9 10.5": ["inhabitation"], "-3.4 10.8 16.0": ["winegrower"], "14.3 7.3 14.4": ["melters"], "0.4 5.5 0.0": ["rerecording"], "4.6 9.4 3.5": ["patricide"], "5.9 22.4 0.0": ["ingraining"], "-3.3 6.7 17.4": ["kuo"], "11.7 12.7 13.3": ["kike", "altocumulus"], "7.3 8.4 9.8": ["kilojoule"], "6.5 6.0 13.6": ["herpetologists"], "-1.7 9.6 1.1": ["recharacterize"], "12.4 3.6 19.8": ["lynxes"], "13.4 9.1 19.7": ["phooey"], "4.4 21.3 7.7": ["airwing"], "0.7 21.1 8.1": ["battlecry"], "7.5 18.8 9.9": ["gulches"], "5.3 4.2 7.6": ["minisodes"], "12.4 4.5 2.3": ["engin"], "6.1 2.5 1.4": ["advertized"], "6.7 8.3 8.0": ["intermingles"], "3.8 9.7 7.2": ["rectally"], "13.9 18.1 10.9": ["ohhhh"], "9.5 16.1 28.1": ["hakapik"], "10.4 12.3 11.1": ["whith"], "15.8 3.0 20.7": ["pompon"], "0.1 4.9 10.9": ["opuses"], "6.8 8.5 -7.3": ["efficency"], "-3.9 -0.4 10.2": ["dextran"], "7.7 7.5 2.8": ["quarterlies"], "-5.8 30.3 4.9": ["servicepeople"], "7.7 10.3 11.0": ["flurried"], "7.0 6.2 14.0": ["teener"], "4.6 -0.8 8.4": ["cathinone"], "12.8 5.5 14.3": ["esplanades"], "6.7 8.4 1.9": ["wasthe"], "16.6 26.3 12.5": ["nimrod"], "8.7 -2.7 -0.2": ["bij"], "7.2 15.0 4.7": ["functionalism"], "4.2 8.6 1.5": ["randomizing"], "6.7 9.4 6.2": ["nunciature"], "13.9 22.0 8.2": ["pusillanimity"], "14.9 16.3 10.7": ["franticly"], "10.3 -0.7 0.0": ["secretin"], "-10.7 1.0 7.7": ["revaccination"], "-3.1 3.3 12.0": ["uncollectibles"], "4.3 9.7 7.8": ["wearier"], "-6.7 8.3 -0.3": ["unascertained"], "-0.6 11.8 11.1": ["misconstruction"], "11.9 14.9 9.1": ["frick"], "28.9 13.6 10.5": ["bestride"], "6.7 -1.7 7.0": ["masterplanned"], "9.2 11.8 10.6": ["fing"], "-2.3 -1.6 2.5": ["transactors"], "3.4 2.3 8.4": ["tuckpointing"], "9.5 8.9 8.4": ["yur"], "2.8 10.1 8.1": ["shoeprints"], "-1.6 15.6 8.4": ["cockier"], "12.5 12.6 41.9": ["needlefish"], "32.1 3.0 4.9": ["whizzkid"], "-6.0 1.8 2.7": ["peated"], "-0.1 9.9 12.3": ["everyting"], "3.9 0.6 6.3": ["nig"], "34.1 5.0 9.2": ["highflier"], "3.9 18.2 8.9": ["germaphobe"], "2.4 4.6 7.8": ["waiata"], "18.2 5.3 17.2": ["venus"], "2.3 10.2 5.8": ["rallys"], "-7.1 9.3 0.4": ["bodystyles"], "14.3 3.2 4.9": ["bedeck"], "-6.2 7.7 7.6": ["bani"], "3.1 -9.0 8.8": ["lse"], "-6.8 3.3 9.5": ["hostellers"], "17.0 9.0 23.2": ["kelpie"], "21.8 11.4 23.1": ["gapes"], "18.4 -6.3 3.2": ["foodservices"], "16.8 11.6 1.5": ["appstore"], "7.4 15.1 17.9": ["unoriginality"], "2.6 4.9 38.9": ["caponata"], "4.5 9.6 2.9": ["authorties"], "6.9 8.5 11.8": ["weasely"], "-1.0 17.5 9.7": ["predetermining"], "-1.5 0.7 7.3": ["dio"], "13.7 10.2 26.4": ["tamarack"], "4.0 19.7 16.3": ["panners"], "1.8 2.2 8.6": ["microencapsulated"], "21.4 6.3 9.7": ["diversifications"], "3.5 13.8 4.7": ["foregrounding"], "-2.0 12.6 8.5": ["tko"], "9.2 14.3 10.8": ["subdirectories"], "9.9 6.7 15.7": ["girlishly"], "-4.3 18.9 7.3": ["decoherence"], "-10.0 11.1 2.1": ["basti"], "11.9 4.5 5.5": ["symbian"], "-7.3 4.8 1.0": ["preemptions"], "2.5 9.1 15.9": ["popouts"], "1.0 7.7 9.4": ["astrophotography"], "2.9 1.2 2.2": ["shlokas"], "8.9 6.7 8.1": ["withy"], "3.3 -1.3 18.5": ["enameling"], "6.3 3.2 2.1": ["moulders"], "8.4 17.6 12.1": ["panderers"], "21.7 -0.8 14.2": ["octomom"], "9.6 12.8 11.8": ["koolaid"], "5.1 6.4 8.2": ["hardtops"], "0.1 -0.0 11.2": ["technopreneurs"], "3.4 8.3 33.3": ["chipotles"], "1.5 20.1 0.3": ["factuality"], "6.0 3.9 -0.1": ["hoteling"], "-12.4 19.1 12.1": ["semiautomatics"], "8.6 7.9 1.3": ["tto"], "10.2 22.0 6.7": ["fibber"], "1.7 9.3 5.4": ["phosphatases"], "10.7 11.9 3.5": ["autoplay"], "3.5 22.1 7.5": ["bastardry"], "-0.3 3.7 24.9": ["affreightment"], "8.4 2.4 17.4": ["prepacked"], "3.7 11.2 20.9": ["haole"], "16.9 4.2 2.0": ["hardsell"], "3.8 9.1 10.1": ["prologues"], "3.7 7.0 -1.2": ["numer"], "13.4 16.3 12.0": ["moonscapes"], "8.9 3.4 -4.8": ["remanufactures"], "7.3 4.8 13.2": ["cheryl"], "8.8 11.7 32.0": ["knockwurst"], "5.9 11.3 10.1": ["anothe"], "6.0 4.5 10.4": ["kvas"], "-2.7 7.8 32.9": ["paranthas"], "7.6 8.4 21.4": ["sua"], "23.1 7.0 9.8": ["shedload"], "9.4 12.5 9.9": ["clamper"], "1.8 25.2 -3.4": ["refuelers"], "5.8 8.5 25.8": ["seabreeze"], "16.7 2.5 8.8": ["yodeler"], "-6.7 10.8 8.1": ["intestacy"], "11.2 7.0 8.2": ["continuingly"], "13.7 22.7 12.8": ["adamantium"], "7.2 14.8 15.1": ["kitesurfer"], "10.9 2.1 1.2": ["controversey"], "6.6 3.7 19.0": ["pasalubong"], "10.9 12.7 13.9": ["gurl"], "0.6 15.6 10.9": ["highwall"], "-3.3 13.5 6.4": ["undesirably"], "9.3 9.3 11.7": ["grep"], "4.0 15.4 24.3": ["zooxanthellae"], "13.0 8.9 19.1": ["smoko"], "9.7 2.2 7.4": ["alcantara"], "8.5 6.8 6.9": ["bert"], "3.8 -1.8 -1.6": ["thepast"], "11.1 4.6 1.0": ["superlight"], "14.6 9.1 14.0": ["flyposting"], "3.8 2.8 7.6": ["rac"], "12.7 7.5 10.3": ["headcover"], "1.9 2.4 7.1": ["copyboy"], "-4.9 16.0 2.3": ["misremembers"], "15.1 10.0 30.0": ["whoopie"], "6.9 28.4 5.0": ["dogmatists"], "11.8 23.8 2.3": ["blindspot"], "6.4 16.2 1.5": ["anyother"], "0.3 7.7 9.2": ["gwabbit"], "2.7 11.6 4.3": ["lifestreaming"], "-1.4 4.0 0.3": ["hyperbilirubinemia"], "9.4 8.3 11.3": ["lav"], "10.0 -7.0 14.8": ["bristol"], "7.2 17.4 17.7": ["superstitiously"], "17.6 13.8 12.1": ["supervolcano"], "6.0 11.5 14.9": ["randoms"], "16.0 6.5 20.9": ["cornstalk"], "4.5 1.2 14.8": ["usuals"], "13.3 17.7 11.1": ["jape"], "-2.9 12.3 3.4": ["transfuse"], "12.4 3.6 44.2": ["milt"], "2.7 8.4 9.3": ["cecum"], "15.3 14.8 24.4": ["dodos"], "2.1 28.1 -2.1": ["inciters"], "6.0 9.6 -3.4": ["dependancy"], "-2.6 8.6 13.9": ["barkada"], "2.3 22.6 3.9": ["balkanisation"], "16.2 16.1 0.0": ["beserk"], "-1.7 13.8 0.3": ["electees"], "14.4 9.1 5.8": ["upbraids"], "13.7 26.4 10.9": ["suckage"], "8.5 17.6 27.3": ["corm"], "13.1 -1.4 2.7": ["egm"], "4.6 19.8 8.6": ["kibbutzniks"], "1.3 2.0 4.3": ["septal"], "6.6 10.8 8.3": ["breezeways"], "-0.7 7.5 5.4": ["renominating"], "2.8 0.2 0.8": ["initialling"], "11.1 14.8 31.5": ["fishfinder"], "4.4 13.6 12.9": ["pierside"], "14.8 2.3 29.9": ["gunnels"], "10.5 14.0 34.4": ["jighead"], "-4.8 2.6 7.1": ["flatting"], "-2.2 6.2 10.5": ["unengaging"], "10.5 -0.6 40.9": ["rillettes"], "2.1 11.7 10.2": ["unassertive"], "8.1 14.0 -0.5": ["reincorporating"], "-5.4 8.0 7.4": ["isocyanate"], "15.5 -0.9 20.7": ["oilcloth"], "0.6 8.3 6.5": ["postponment"], "7.3 12.6 8.4": ["uv"], "15.8 14.7 39.7": ["mealworm"], "-1.9 8.1 10.0": ["delevering"], "4.9 10.7 10.8": ["gyun"], "10.5 1.4 15.3": ["cardboards"], "2.2 25.8 4.0": ["evader"], "-2.8 1.3 10.3": ["ottawa"], "12.1 12.0 27.5": ["quoits"], "5.4 2.2 5.3": ["unretirement"], "18.1 8.5 37.6": ["salal"], "16.4 -5.3 -2.9": ["sponsered"], "0.4 30.0 10.6": ["endgames"], "3.0 7.0 -4.5": ["prosector"], "14.5 6.1 13.6": ["twizzle"], "13.0 10.9 12.3": ["groveled"], "-3.9 32.6 6.8": ["nonhostile"], "5.6 17.7 5.5": ["precipitately"], "5.5 12.5 10.5": ["hdd", "uncompetitiveness"], "7.7 15.4 18.0": ["cain"], "-8.6 4.0 2.0": ["invigilation"], "0.4 -5.4 9.4": ["bw"], "6.6 5.4 2.6": ["refigured"], "9.0 5.2 9.7": ["teashops"], "5.3 0.6 14.8": ["caliente"], "6.4 3.1 20.7": ["georgettes"], "-1.9 9.7 6.9": ["personalties"], "17.0 9.1 7.5": ["vegetating"], "15.7 5.7 21.2": ["lacework"], "-4.7 7.1 -3.7": ["chaplin"], "17.0 2.1 10.2": ["gigantically"], "-1.3 11.7 9.6": ["imprecisely"], "-0.3 4.7 8.8": ["guaifenesin"], "12.6 18.5 3.9": ["bribers"], "-0.2 12.1 7.2": ["durbars"], "9.6 17.4 17.8": ["pollinates"], "2.5 9.3 25.5": ["undercooking"], "-4.6 8.4 26.0": ["liveaboard"], "17.8 13.8 15.8": ["twixt"], "4.2 16.3 15.2": ["monopod"], "-6.2 6.2 4.9": ["hydroxychloroquine"], "4.3 21.2 -1.5": ["illumine"], "18.8 26.0 10.1": ["kneecapping"], "9.3 4.3 10.6": ["aformentioned"], "8.6 10.7 -1.2": ["knockbacks"], "9.4 14.2 5.3": ["outslugging"], "2.6 22.5 6.9": ["obloquy"], "-4.2 16.9 -1.5": ["favourability"], "5.1 -0.9 13.6": ["desalting"], "7.0 22.2 7.6": ["gadgetgurus"], "-4.1 10.5 6.1": ["signalcaller"], "1.0 5.3 15.0": ["drillable"], "16.4 23.5 11.6": ["wiimote"], "6.0 25.7 12.5": ["vengefulness"], "7.4 8.9 9.6": ["underbidding"], "12.1 4.7 10.8": ["tln"], "-10.5 -1.7 7.5": ["suboxone"], "7.2 5.9 24.2": ["incisor"], "8.6 15.2 7.3": ["heteronormative"], "11.4 -0.7 18.7": ["dancesport"], "4.4 12.3 28.4": ["upwellings"], "13.6 13.5 0.8": ["electrophoretic"], "9.1 -0.7 22.3": ["slo"], "8.6 0.8 15.0": ["troughing"], "20.2 24.1 19.5": ["underbellies"], "2.1 25.1 8.1": ["outthought"], "0.7 16.0 10.0": ["suffocatingly"], "5.5 20.4 7.0": ["geofencing"], "5.3 7.2 13.4": ["tete"], "5.6 11.7 36.5": ["damselfly"], "-1.7 19.5 11.0": ["dost"], "5.3 8.9 12.2": ["umbilicus"], "13.7 17.2 1.7": ["unironically"], "18.1 13.1 21.1": ["gooses"], "-9.1 27.9 -1.6": ["takfiri"], "10.3 2.0 19.7": ["restuarants"], "18.7 15.9 6.4": ["blipping"], "10.1 1.2 14.4": ["nightcaps"], "-10.0 10.5 5.3": ["colleages"], "1.1 6.1 7.8": ["porosities"], "-2.0 3.7 4.5": ["disfavoured"], "-8.2 5.4 6.3": ["dikgosi"], "3.1 10.5 2.5": ["outreached"], "6.8 -1.8 12.2": ["dealflow"], "8.8 5.6 7.3": ["minimill"], "-1.2 9.9 31.8": ["emergers"], "14.0 13.1 4.1": ["twitterverse"], "-3.4 7.5 4.8": ["biglaw"], "-2.0 0.1 -0.2": ["polyamides"], "5.5 -0.1 2.8": ["labelers"], "-9.1 2.8 2.8": ["factfinding"], "1.6 27.3 4.0": ["collaterally"], "14.7 22.2 9.8": ["bomblet"], "9.8 25.7 6.9": ["theocrat"], "-3.0 6.7 13.8": ["anhedonia"], "-6.1 9.0 -2.3": ["articled"], "15.4 17.6 15.7": ["pustule"], "-5.2 4.6 7.9": ["ordinands"], "8.6 17.9 11.4": ["backroad"], "15.8 21.3 37.3": ["speargun"], "-1.4 7.1 8.6": ["skarns"], "20.3 13.1 22.9": ["licker"], "-0.1 8.7 17.8": ["intercropping"], "7.4 4.2 32.6": ["serrano"], "1.9 15.6 14.4": ["bhaiya"], "2.7 2.7 -0.1": ["hakia"], "-7.2 10.9 12.1": ["occupationally"], "10.0 9.8 13.5": ["operatically"], "13.1 26.9 14.8": ["obsequiously"], "2.3 24.6 16.7": ["gsp"], "5.1 19.8 10.0": ["deathbeds"], "-0.5 6.1 22.3": ["gua"], "-3.0 0.3 20.3": ["hoggs"], "-3.8 11.0 9.0": ["endoscopists"], "1.7 15.4 6.9": ["coheres"], "11.8 6.2 17.3": ["noodled"], "14.1 6.0 8.4": ["homevideo"], "-2.1 4.3 -5.0": ["frst"], "2.5 9.8 6.8": ["misstepped"], "-1.8 -6.4 11.4": ["camperships"], "3.7 7.3 0.8": ["banlieue"], "9.6 17.6 8.3": ["lawgiver"], "5.3 2.0 14.6": ["cholis"], "3.3 5.6 15.4": ["subcabinet"], "3.6 13.6 11.6": ["rhymer"], "11.4 2.4 13.5": ["watson"], "6.0 18.2 4.1": ["inflexibly"], "-7.8 21.6 -5.7": ["debriefers"], "13.9 10.6 12.6": ["microdots"], "7.8 -0.6 3.1": ["ilumisys"], "1.9 10.4 0.7": ["scaleability"], "3.4 14.3 -5.8": ["belabour"], "13.3 34.7 29.1": ["grenadier"], "12.4 13.5 12.6": ["spidered"], "1.7 9.4 16.2": ["swarf"], "15.8 8.3 3.9": ["nonbanking"], "8.8 18.2 23.5": ["stamen"], "4.6 8.8 9.4": ["idiosyncratically"], "21.5 7.3 5.8": ["jetmaker"], "12.8 12.2 8.4": ["tokamak"], "16.1 10.1 32.8": ["quackers"], "1.2 0.4 0.9": ["pagoclone"], "10.1 8.5 26.8": ["fiord"], "2.5 8.3 15.4": ["cowpox"], "14.1 11.6 7.7": ["weathergirl"], "-1.7 10.5 14.5": ["disjoint"], "-10.6 1.6 2.7": ["committer"], "5.4 17.1 10.8": ["contrarianism"], "9.4 6.5 13.8": ["tonneau"], "0.0 -8.8 2.9": ["tollfree"], "9.1 2.8 3.2": ["verus"], "-1.3 14.9 15.4": ["intercutting"], "5.5 8.1 0.5": ["unlikley"], "6.6 15.5 10.9": ["miscalculates"], "-7.8 2.3 -2.7": ["interprofessional"], "2.9 -2.4 10.6": ["vip"], "23.2 9.6 19.1": ["bucktoothed"], "-6.3 1.5 0.0": ["reexaminations"], "1.2 2.0 8.1": ["hesistant"], "8.3 10.6 10.8": ["ganglion"], "11.8 9.3 21.9": ["nob"], "7.8 7.1 22.0": ["bhog"], "0.4 10.1 5.3": ["overspeed"], "11.3 8.6 4.7": ["figleaf"], "1.2 -6.8 10.2": ["xl"], "-0.7 1.3 8.4": ["adjustables"], "-1.4 6.2 -2.1": ["peforming"], "7.8 -0.5 7.8": ["liri"], "7.5 16.5 10.0": ["geotargeting"], "5.0 4.3 37.0": ["porchetta"], "8.0 1.7 25.9": ["tarte"], "-1.5 9.0 -3.6": ["halogenated"], "12.2 6.1 5.1": ["headiest"], "9.7 17.2 13.4": ["brushland"], "0.2 17.3 13.7": ["miscounting"], "-1.1 20.1 12.1": ["mainstreamers"], "3.8 3.0 48.9": ["unagi"], "-0.7 12.7 11.3": ["namo"], "2.8 15.0 21.1": ["poultices"], "5.0 1.3 4.2": ["ahl"], "7.8 17.3 14.5": ["armlock"], "7.5 -1.7 16.9": ["methamidophos"], "-5.7 5.8 4.6": ["demurring"], "12.9 5.3 38.2": ["schoolie"], "9.2 15.6 16.9": ["bairn"], "4.6 12.9 15.1": ["whiteheads"], "-2.8 10.8 6.1": ["maldistribution"], "7.9 4.9 10.6": ["remodelings"], "-3.6 16.9 5.3": ["ventilations"], "4.2 11.0 7.6": ["unabatedly"], "9.8 16.4 14.4": ["geoid"], "-2.4 7.7 6.2": ["subnormal"], "0.4 0.3 5.5": ["microinverters"], "4.3 4.4 5.1": ["stereolithography"], "4.2 5.5 2.1": ["sharepoint"], "16.4 0.5 5.1": ["groupwide"], "-5.1 4.9 12.5": ["sternal"], "-2.8 32.2 2.8": ["intellegence"], "8.8 -1.6 10.4": ["heidi"], "6.9 7.0 1.9": ["liberalizes"], "11.5 10.1 16.8": ["spazzy"], "6.9 9.7 10.1": ["sibilant"], "13.9 5.2 14.2": ["duffle"], "7.5 11.2 16.2": ["saltpeter"], "8.6 16.5 10.2": ["hayseeds"], "12.9 9.1 12.9": ["numpties"], "6.5 11.3 7.8": ["blathers"], "-6.0 8.2 2.6": ["hareidi"], "-0.6 5.1 9.5": ["loratadine"], "0.2 8.6 9.6": ["sundays"], "-1.9 5.9 9.8": ["heliskiing"], "7.1 1.8 31.8": ["orecchiette"], "6.7 12.1 6.2": ["isavuconazole"], "10.7 19.6 11.6": ["impolitely"], "10.9 10.6 5.9": ["airbrushes"], "0.8 -1.9 4.9": ["postgraduation"], "14.0 8.7 4.7": ["governnment"], "6.7 16.4 12.9": ["diaster"], "6.5 0.9 8.1": ["bedlinen"], "5.0 11.7 26.5": ["coastland"], "7.4 11.2 3.9": ["resemblence"], "6.7 7.7 14.4": ["superlabs"], "-2.7 6.4 4.8": ["reedman"], "-3.5 6.3 14.6": ["potassic"], "7.4 1.3 12.8": ["mitchell"], "23.9 8.5 24.0": ["duckies"], "12.0 6.5 17.9": ["prises"], "0.3 2.5 2.9": ["lagos"], "-4.7 1.8 25.4": ["soyameal"], "6.6 8.2 5.7": ["apaziquone"], "9.4 6.2 12.8": ["sockless"], "-2.4 8.6 13.4": ["electrocautery"], "-7.9 0.4 -7.1": ["chairpersonship"], "2.8 15.1 15.7": ["glumness"], "11.4 -1.5 10.0": ["oday"], "8.9 10.8 25.5": ["larders"], "5.1 23.2 7.3": ["armouring"], "3.1 11.9 8.9": ["timezones"], "-0.7 5.2 6.3": ["preflighting"], "-0.1 20.3 12.6": ["unforgiven"], "8.9 9.4 19.6": ["malamute"], "7.3 18.4 9.0": ["restrictionists"], "7.4 12.0 -0.0": ["interferring"], "12.8 12.5 9.9": ["reprehensibility"], "2.4 19.7 3.7": ["faithlessness"], "10.6 16.8 14.6": ["risings"], "-4.8 9.1 12.1": ["simcha"], "3.7 12.2 2.8": ["vicitms"], "2.3 3.1 0.5": ["miscoded"], "9.5 12.5 11.8": ["cambered"], "5.9 0.7 20.2": ["minibottle"], "6.0 7.7 13.0": ["unstuffy"], "11.8 12.2 7.4": ["tricorder"], "10.9 -2.9 -3.3": ["servic"], "1.4 19.6 6.5": ["avoider"], "0.5 5.1 12.3": ["steerer"], "3.1 11.1 9.4": ["insanitary"], "-1.7 1.1 -1.2": ["dbx"], "3.8 4.1 1.6": ["threee"], "3.6 0.2 21.1": ["folklife"], "0.4 -1.4 11.1": ["skort"], "-0.2 0.7 7.0": ["demineralization"], "6.3 14.3 12.3": ["exquisiteness"], "2.1 19.6 0.8": ["somalia"], "2.5 3.7 21.8": ["merienda"], "-11.3 11.5 8.0": ["nonparticipation"], "7.4 10.8 7.1": ["cannier"], "6.1 15.2 15.5": ["strokemakers"], "9.9 16.1 3.9": ["abhorring"], "-11.8 5.5 4.9": ["instructionally"], "12.8 14.3 18.5": ["strumpet"], "15.2 19.4 20.8": ["pallino"], "9.0 23.1 27.0": ["mealybug"], "6.4 6.3 16.2": ["collins"], "7.8 1.2 24.8": ["paddleboards"], "2.6 8.0 6.2": ["ureters"], "4.5 -0.2 13.8": ["nef"], "13.7 15.7 21.6": ["unicellular"], "5.9 15.1 3.3": ["polarises"], "4.6 21.0 0.7": ["interposing"], "9.5 22.9 4.6": ["beasting"], "19.4 10.7 20.9": ["sno"], "2.3 11.1 -1.7": ["depoliticised"], "4.7 9.0 4.0": ["tardily"], "10.1 6.8 0.9": ["eeking"], "19.2 5.5 3.6": ["dodgier"], "-4.0 1.5 9.7": ["beneficiated"], "2.0 15.2 17.7": ["wheelin"], "-0.0 17.3 32.4": ["huntable"], "4.6 3.5 1.5": ["kulula"], "15.3 12.4 19.4": ["ponce"], "5.7 8.5 1.5": ["campagin"], "20.1 22.7 13.2": ["earthward"], "3.7 14.3 14.6": ["lithologic"], "13.1 1.5 4.8": ["unbinding"], "5.9 5.2 20.8": ["fixative"], "5.5 1.8 17.6": ["annie"], "3.2 12.8 14.3": ["daytraders"], "7.6 18.0 8.5": ["traceurs"], "3.6 4.8 8.0": ["humidified"], "-3.0 5.6 1.2": ["pranayam"], "-6.9 1.9 6.0": ["fractionals"], "9.3 10.2 14.9": ["chainrings"], "4.2 4.5 24.9": ["drydocked"], "-8.2 3.3 11.4": ["fluorides"], "7.6 12.7 16.9": ["overfull"], "-2.6 -8.3 6.7": ["sixmonth"], "14.4 22.8 12.2": ["goddammit"], "2.0 18.4 2.2": ["karsevaks"], "9.5 12.2 9.8": ["cuddlier"], "10.8 11.8 10.2": ["lustfully"], "8.0 5.0 26.3": ["flavorsome"], "-7.6 -0.4 8.8": ["deliquency"], "2.3 8.0 3.1": ["alzheimers"], "14.7 6.4 7.7": ["exhib"], "20.2 9.3 21.3": ["oilrig"], "17.9 14.3 4.7": ["tmobile"], "-1.0 8.2 -3.8": ["routable"], "-11.1 10.0 19.1": ["vinifera"], "4.3 5.5 20.5": ["kane"], "2.5 8.3 36.1": ["potpie"], "3.6 13.8 0.7": ["exceptionality"], "23.3 12.0 35.0": ["saltie"], "7.2 9.2 7.7": ["metabolomic"], "-1.8 16.7 21.9": ["easterlies"], "3.0 14.9 28.1": ["pintos"], "9.0 9.4 9.9": ["wana"], "6.8 15.5 17.4": ["purl"], "-1.8 2.9 0.4": ["myfoxdc"], "-2.9 7.1 17.8": ["macerate"], "8.0 1.4 26.9": ["titmice"], "1.9 15.6 15.0": ["wiregrass"], "12.9 9.1 23.7": ["yummiest"], "11.4 14.8 16.1": ["supermaxi"], "10.1 10.8 8.3": ["intheir"], "9.6 7.9 1.9": ["inscribes"], "19.8 10.9 34.3": ["puffballs"], "-1.3 7.0 8.0": ["compressibility"], "4.6 6.4 13.6": ["chromophore"], "-6.3 13.4 25.7": ["caramelization"], "6.6 9.9 14.7": ["waystation"], "2.8 6.4 10.5": ["hillwalking"], "0.3 5.4 9.5": ["anneal"], "9.2 5.6 8.6": ["etf"], "2.8 10.9 12.4": ["bivy"], "5.2 10.3 11.3": ["porphyrins"], "4.7 17.0 13.5": ["mulish"], "23.8 5.9 31.4": ["cornflake"], "6.6 7.3 11.4": ["vm"], "3.7 4.3 16.8": ["regionality"], "4.1 16.4 -3.2": ["indoctrinates"], "3.9 2.3 30.8": ["pestos"], "6.1 7.3 10.1": ["mort"], "12.1 10.3 17.5": ["tetrahedral"], "-1.4 10.0 2.3": ["allosteric"], "-2.9 9.9 0.9": ["baluns"], "10.3 0.9 32.9": ["balut"], "7.8 0.3 6.3": ["mejor"], "3.0 9.3 20.4": ["kabab"], "0.9 7.6 1.6": ["upconvert"], "1.3 8.7 21.3": ["ryokan"], "6.8 1.3 -1.3": ["verison"], "2.2 6.2 2.3": ["aliphatic"], "3.1 11.3 8.0": ["contriteness"], "10.6 8.6 8.5": ["ringmasters"], "13.0 11.3 10.5": ["sheikhdoms"], "10.6 7.0 18.1": ["biopharming"], "1.2 3.5 5.8": ["ribose"], "-8.9 4.8 7.3": ["informaiton"], "-2.6 7.9 10.0": ["seasonless"], "9.1 1.1 28.7": ["anthurium"], "1.5 11.8 6.7": ["rubout"], "-2.6 4.6 8.9": ["iqama"], "-1.5 -2.5 -2.1": ["reax"], "15.6 9.5 29.5": ["ammonites"], "6.4 -2.4 0.2": ["healthymagination"], "4.3 4.0 2.1": ["sentimentalized"], "-0.1 6.7 7.3": ["tropospheric"], "7.9 2.8 7.3": ["doublecheck"], "10.9 22.7 5.7": ["backlands"], "1.1 6.5 -3.3": ["congestive"], "-0.7 27.6 17.0": ["fundamentalisms"], "-2.8 15.9 1.4": ["suppressions"], "3.2 36.3 11.9": ["respawning"], "13.5 4.6 7.2": ["lithographer"], "8.9 18.1 6.6": ["codebreaker"], "12.0 16.9 19.4": ["parangs"], "9.3 17.6 31.8": ["bustard"], "1.4 6.9 14.9": ["buhay"], "0.7 -2.5 5.3": ["postdated"], "9.7 4.9 10.8": ["voluptuously"], "11.9 14.2 40.9": ["piscatorial"], "15.8 11.2 14.4": ["granuloma"], "4.9 -1.1 7.5": ["hydrocolloid"], "-0.7 1.6 0.4": ["lifestage"], "-2.5 8.4 9.0": ["ulpan"], "3.5 3.7 18.2": ["bbs"], "-0.6 1.1 3.1": ["dualled"], "4.2 20.6 0.9": ["mutliple"], "0.5 11.6 17.3": ["erythrocytes"], "-3.1 1.7 5.2": ["incorporator"], "8.3 3.3 9.6": ["cajon"], "5.6 -1.2 9.5": ["peps"], "1.5 -1.4 9.8": ["oleic"], "2.8 3.8 10.5": ["businessowners"], "10.0 -4.2 19.4": ["ceilidhs"], "4.5 5.0 4.8": ["proceedures"], "0.4 15.5 5.9": ["avowals"], "4.1 15.1 15.7": ["dropshipping"], "5.0 4.5 -1.9": ["acheivements"], "6.5 11.4 7.0": ["gurs"], "4.0 -2.6 10.6": ["flo"], "9.4 2.7 8.4": ["predesigned"], "12.4 17.5 19.0": ["grubbers"], "10.1 -0.9 13.7": ["pouffy"], "5.7 6.6 19.2": ["merbau"], "-6.1 0.9 1.9": ["gemfibrozil"], "0.3 20.9 20.6": ["blackgrass"], "1.2 16.3 7.0": ["flatfoot"], "12.8 1.3 10.6": ["shoppes"], "21.2 6.5 6.8": ["shareprice"], "0.7 -2.4 5.5": ["cle"], "-5.2 11.3 0.0": ["fictionalization"], "8.7 8.1 7.3": ["visuospatial"], "2.7 0.9 7.7": ["domaine"], "4.9 8.5 1.3": ["soll"], "5.7 -1.4 9.4": ["curtainwall"], "4.3 5.2 7.1": ["admixtures"], "1.7 3.3 -4.3": ["capnography"], "3.7 0.2 39.4": ["chateaubriand"], "14.4 0.8 18.4": ["housedress"], "6.4 -0.2 16.9": ["nem"], "12.3 -3.5 -0.1": ["woundcare"], "11.9 6.5 3.4": ["scrawlings"], "5.6 2.4 6.6": ["freebees"], "7.7 26.2 11.6": ["worlders"], "-2.0 4.2 -0.6": ["leviable"], "20.8 10.3 17.1": ["treadle"], "2.6 18.1 5.9": ["protracting"], "17.8 2.6 10.7": ["durante"], "17.1 10.6 6.0": ["hypnotising"], "0.1 8.8 9.2": ["superpole"], "10.5 -1.8 9.9": ["lathers"], "-5.9 10.6 10.1": ["topoisomerase"], "-0.4 0.9 14.5": ["ceramists"], "9.0 12.4 40.2": ["salties"], "5.0 13.5 3.7": ["geeing"], "5.1 11.3 12.7": ["returnables"], "2.5 12.6 10.5": ["hese"], "23.6 -4.3 3.9": ["digitial"], "7.2 32.8 11.6": ["barbarically"], "-0.5 6.6 3.8": ["municipalization"], "-6.8 10.2 0.4": ["personaly"], "10.1 5.6 16.8": ["gadabout"], "14.3 5.3 10.3": ["stereophonic"], "1.8 -4.9 11.1": ["prerecession"], "-4.3 1.8 8.9": ["granddam"], "15.4 16.8 10.5": ["enrapturing"], "-4.1 17.0 0.7": ["creedal"], "19.6 6.9 14.5": ["hatbox"], "6.4 6.3 16.9": ["calcify"], "8.2 12.0 32.0": ["picadillo"], "3.0 10.3 14.9": ["sirenomelia"], "3.3 -5.3 11.2": ["dri"], "-0.2 34.5 16.9": ["lostness"], "-1.2 19.6 20.5": ["iciness"], "10.5 17.3 13.9": ["fleetness"], "7.9 8.1 9.4": ["kore"], "6.9 12.1 10.4": ["booter"], "13.2 12.1 10.8": ["unhinging"], "0.2 -12.0 9.8": ["soh"], "2.5 18.5 10.3": ["deterent"], "6.6 16.0 8.7": ["logarithm"], "10.8 -2.7 5.6": ["racey"], "3.5 -3.5 1.5": ["theindustry"], "4.8 -0.9 -1.8": ["receipting"], "2.9 5.2 5.7": ["dreamier"], "10.7 4.0 40.6": ["sweetbread"], "6.5 2.8 13.8": ["tassles"], "-2.1 -6.4 12.2": ["fieldtrips"], "3.4 15.2 10.4": ["trembler"], "13.1 16.5 9.9": ["artlessly"], "0.6 5.6 0.9": ["permenant"], "5.5 7.4 2.7": ["nanofibres"], "7.3 9.1 14.8": ["carryings"], "5.0 15.4 6.3": ["fanfiction"], "7.3 10.8 11.5": ["bioaccumulate"], "-1.3 15.7 20.1": ["slurve"], "4.2 5.3 11.5": ["geun"], "-1.7 11.4 10.7": ["lignocellulose"], "20.2 14.0 8.9": ["pentagrams"], "-0.7 1.0 3.1": ["dms"], "-1.3 1.9 4.9": ["costeffective"], "-5.5 -2.2 1.8": ["forewords"], "11.0 11.7 11.6": ["mixmaster"], "2.8 14.7 9.6": ["phonon"], "1.1 8.2 6.1": ["foregrounded"], "3.4 5.5 1.6": ["indepedent"], "0.0 -0.9 -4.6": ["mainstreams"], "6.8 10.8 8.8": ["newsmedia"], "9.4 6.7 5.4": ["semipublic"], "2.5 11.3 11.2": ["transected"], "5.4 7.0 21.5": ["jallikattu"], "1.8 3.4 4.1": ["batt"], "22.2 18.7 19.1": ["crawly"], "11.5 6.3 17.3": ["patchiness"], "-4.4 -3.8 2.6": ["reoffered"], "3.1 15.1 5.7": ["crunchtime"], "3.3 16.2 12.1": ["gaza"], "8.3 6.0 11.1": ["losin"], "3.6 0.8 4.4": ["leurs"], "-3.4 2.8 12.9": ["boite"], "4.3 4.5 13.8": ["hsien"], "4.4 9.6 5.4": ["rereleases"], "18.5 4.8 23.3": ["jacaranda"], "2.6 3.8 5.3": ["almshouses"], "5.2 10.2 38.6": ["poblanos"], "-0.8 11.4 22.6": ["dhoni"], "-3.3 3.2 -5.9": ["llinois"], "7.9 14.3 10.8": ["blazin"], "25.4 4.7 20.9": ["papier"], "0.8 1.2 1.2": ["tetrabenazine"], "4.1 14.6 5.1": ["airbridge"], "0.5 7.4 2.6": ["epothilone"], "8.1 9.2 12.8": ["chirpily"], "7.6 -2.5 0.1": ["muncipal"], "11.4 -3.1 14.4": ["jacquards"], "8.2 3.6 6.4": ["parters"], "5.3 11.1 25.5": ["sambhar"], "3.4 9.6 11.7": ["smoochy"], "3.8 12.6 15.7": ["toxicant"], "0.6 13.9 32.8": ["macroalgae"], "2.2 4.6 4.9": ["figitumumab"], "12.4 -12.2 -5.8": ["recenlty"], "4.9 2.6 13.8": ["unloader"], "8.5 16.1 9.4": ["thumbwheel"], "19.5 13.5 6.5": ["hooplah"], "4.0 14.4 10.0": ["monarchial"], "-6.9 0.2 -7.2": ["tranferred"], "6.1 11.3 7.1": ["appals"], "1.1 8.9 8.5": ["vaginitis"], "6.5 8.4 42.3": ["pikeminnow"], "3.8 0.0 6.0": ["volleyballer"], "21.6 10.1 15.5": ["snowglobe"], "2.1 2.3 9.3": ["economized"], "7.6 4.7 21.9": ["pinny"], "10.3 16.1 8.2": ["gossipmongers"], "-6.5 21.7 7.8": ["bunters"], "-5.6 -1.2 7.2": ["ammendments"], "6.5 4.6 12.5": ["flightseeing"], "3.0 9.4 9.2": ["custirsen"], "-2.0 9.3 13.9": ["zamindars"], "8.6 20.2 6.5": ["elses"], "-0.0 1.2 -0.7": ["atacicept"], "7.6 9.8 22.8": ["angelica"], "2.9 3.2 5.8": ["elotuzumab"], "7.8 3.9 7.7": ["slitter"], "20.1 25.4 11.0": ["sneakiest"], "5.9 5.7 9.3": ["classily"], "-2.9 0.8 8.6": ["mmol"], "7.1 15.9 -0.8": ["hierachy"], "-3.4 9.0 16.0": ["aina"], "10.5 23.1 8.6": ["airdropping"], "2.8 14.0 1.2": ["reengaging"], "13.7 1.3 6.4": ["blueprinting"], "7.0 31.0 2.1": ["millitary"], "11.0 15.1 9.8": ["kleptomaniacs"], "-0.5 8.5 8.2": ["hopefull"], "5.9 16.8 42.6": ["gadwalls"], "27.1 14.5 14.6": ["beermakers"], "-2.0 5.2 9.5": ["karnataka"], "0.3 9.6 15.5": ["calpain"], "24.8 4.2 21.3": ["formica"], "8.5 8.0 4.7": ["appropiate"], "0.1 2.3 9.9": ["terbinafine"], "5.2 -0.1 8.4": ["pharmacopoeia"], "3.0 4.6 5.7": ["notre"], "-5.4 8.6 6.3": ["deduplicated"], "3.2 8.0 3.5": ["comparitively"], "-2.7 11.6 7.0": ["watchability"], "22.2 1.2 -0.9": ["compan"], "4.2 6.1 29.5": ["tian"], "0.6 19.4 9.7": ["pushiness"], "10.4 0.2 11.5": ["jh"], "6.2 24.4 10.8": ["wiliest"], "12.7 13.5 12.2": ["manipulable"], "0.5 9.8 11.4": ["sesamoid"], "-6.7 1.9 12.2": ["eason"], "13.7 17.9 22.2": ["leprous"], "11.0 9.8 13.7": ["polaroid"], "2.6 8.2 19.2": ["parings"], "7.6 12.3 4.6": ["unchosen"], "-8.3 0.2 -1.1": ["repectively"], "9.1 7.9 9.0": ["lettin"], "6.8 4.1 -6.2": ["publicises"], "-0.9 14.9 11.4": ["dilemna"], "9.9 -0.5 23.0": ["cabochon"], "-3.8 6.2 9.5": ["sesaon"], "3.4 9.0 1.8": ["analogize"], "-5.2 9.5 3.4": ["resending"], "2.6 7.1 12.4": ["bactrim"], "20.9 -0.7 18.9": ["processers"], "0.0 13.9 12.7": ["fallbacks"], "14.2 31.9 15.0": ["railgun"], "-1.4 13.5 19.2": ["muddiness"], "-5.0 4.9 1.4": ["thermistors"], "5.9 -1.9 4.9": ["voir"], "-7.2 7.9 4.9": ["acclamations"], "15.5 10.8 23.0": ["barque"], "22.0 14.2 21.8": ["loogie"], "30.8 15.0 28.6": ["toadstool"], "-4.6 7.9 5.4": ["synovitis"], "-6.5 1.5 6.2": ["dronabinol"], "12.6 18.4 14.6": ["devilry"], "-2.9 7.7 16.3": ["nama"], "16.9 9.7 15.0": ["blech"], "17.4 -1.7 20.4": ["aardvarks"], "0.5 8.7 3.1": ["throug"], "10.7 2.6 1.1": ["switchgears"], "4.8 19.0 5.5": ["unreadiness"], "10.8 3.9 14.0": ["subnotebooks"], "-3.8 16.3 5.3": ["communalisation"], "7.5 3.5 0.4": ["nanoelectronic"], "9.0 7.5 6.9": ["andwe"], "0.8 23.9 8.7": ["coequal"], "8.6 9.1 23.3": ["scatterings"], "2.1 1.3 12.1": ["mismo"], "-8.9 13.4 4.4": ["pacenotes"], "2.0 8.7 24.0": ["filberts"], "4.2 11.9 10.2": ["phoneme"], "12.8 5.9 14.3": ["biotechnologists"], "-6.6 7.6 3.4": ["polyneuropathy"], "1.4 1.7 1.9": ["dari"], "-6.6 23.5 0.1": ["undeterminable"], "21.3 6.8 12.9": ["cloners"], "0.8 9.3 -0.8": ["crewcuts"], "15.9 6.2 13.3": ["bedhead"], "9.5 14.2 23.8": ["wardroom"], "7.7 5.1 13.7": ["solaris"], "3.7 3.6 17.7": ["grillz"], "2.1 4.7 -7.2": ["reponded"], "0.4 8.1 10.2": ["snarking"], "11.9 3.7 13.2": ["debian"], "-5.9 27.9 5.5": ["determent"], "12.1 -4.5 5.5": ["hackathon"], "13.2 7.0 8.9": ["phials"], "13.6 13.7 16.1": ["wiv"], "14.3 8.4 15.7": ["clogger"], "2.6 24.4 5.2": ["bunkmate"], "16.1 6.3 9.5": ["caulkers"], "4.9 6.2 6.2": ["siempre"], "0.1 5.7 6.3": ["attainability"], "9.4 3.7 12.8": ["mayby"], "5.8 4.7 20.6": ["mycologist"], "10.9 14.8 12.1": ["adventuress"], "5.7 10.0 6.2": ["uninterruptible"], "3.4 -2.1 12.3": ["nonathletic"], "13.9 16.3 18.3": ["deforesting"], "10.8 17.1 11.3": ["freakiness"], "14.1 -0.0 15.2": ["fakie"], "4.0 15.9 12.6": ["gonged"], "9.1 0.5 16.6": ["tapwater"], "4.9 10.1 1.2": ["completley"], "3.6 12.9 4.4": ["fd"], "-4.4 2.4 19.8": ["amon"], "1.2 4.6 6.3": ["batholith"], "-2.7 -0.2 16.1": ["millings"], "4.8 9.8 5.8": ["spead"], "12.4 4.4 7.1": ["netherlands"], "25.4 9.5 21.1": ["waxen"], "7.1 11.4 31.2": ["poundcake"], "8.4 1.9 17.7": ["rowan"], "4.8 4.7 9.5": ["photoluminescence"], "1.7 14.0 11.9": ["buyrates"], "-6.8 6.4 10.4": ["khayal"], "-10.1 4.3 4.8": ["concelebrate"], "7.3 -0.8 12.6": ["spritzes"], "12.2 15.3 10.2": ["bloviators"], "7.3 5.9 13.3": ["pittsburgh"], "10.5 12.4 11.5": ["leftmost"], "7.5 7.9 5.9": ["recategorisation"], "20.2 12.7 20.1": ["cuboid"], "4.2 4.7 22.8": ["donald"], "-4.3 6.3 6.3": ["pharmacoeconomics"], "-10.0 14.0 3.8": ["lieve"], "7.2 7.2 14.3": ["mmmmm"], "15.0 17.1 14.8": ["flagstaff"], "1.0 6.5 9.4": ["harrumphs"], "19.0 5.4 13.0": ["toddles"], "22.5 8.9 6.1": ["maket"], "9.5 10.3 9.6": ["uhhhh"], "-14.1 24.5 4.8": ["reenlisting"], "-3.2 5.1 9.5": ["fol"], "0.7 27.6 1.3": ["exfiltration"], "9.6 11.1 9.3": ["sheepfold"], "4.5 7.0 8.0": ["embezzles"], "4.5 19.6 -2.2": ["intelligibly"], "7.0 7.3 -1.5": ["starer"], "2.5 26.4 2.2": ["insurrectionist"], "9.2 13.6 11.3": ["boybands"], "10.9 1.6 7.0": ["semagacestat"], "0.7 8.7 10.2": ["melisma"], "-8.7 -2.4 3.9": ["meeeting"], "-0.4 7.1 18.1": ["notecard"], "-2.3 -10.1 0.6": ["nance"], "6.2 20.3 8.4": ["chemiluminescent"], "8.5 10.6 17.8": ["ligers"], "17.8 12.6 12.8": ["thrillseekers"], "-7.5 5.1 9.6": ["burgess"], "13.3 12.9 6.9": ["typosquatting"], "5.0 -10.7 3.9": ["devel"], "-4.5 11.1 8.7": ["gaols"], "5.5 1.3 9.1": ["youn"], "14.5 10.4 15.1": ["birdcalls", "tesoro"], "7.7 0.9 11.9": ["bagong"], "8.0 4.4 19.3": ["alu"], "11.1 13.1 21.8": ["mistral"], "7.8 4.8 22.4": ["coonhound"], "12.2 10.8 24.2": ["nandina"], "13.3 7.6 18.5": ["jerkin"], "3.6 9.2 17.1": ["overdress"], "6.2 3.6 9.3": ["pennywhistle"], "4.8 12.2 3.1": ["beign"], "3.0 13.5 9.5": ["tattles"], "6.1 7.0 24.9": ["albumen"], "4.6 0.9 3.6": ["phenylpropanolamine"], "11.1 2.2 10.3": ["cush"], "9.0 5.5 16.2": ["guid"], "-6.7 2.4 3.7": ["atherothrombosis"], "0.0 1.3 3.6": ["valuators"], "0.8 13.3 2.5": ["intenders"], "4.9 11.6 1.5": ["repartition"], "6.3 12.9 1.6": ["freeload"], "10.4 14.1 17.6": ["boobie"], "16.2 6.2 7.5": ["webkit"], "5.9 14.4 11.6": ["zocalo"], "9.9 3.1 8.5": ["shopgirl"], "3.2 2.7 1.5": ["abot"], "4.4 10.2 2.9": ["declamations"], "-0.7 12.3 1.4": ["expositional"], "5.2 9.6 9.3": ["definer"], "0.4 25.6 20.0": ["broadheads"], "0.5 7.3 15.7": ["equable"], "4.7 2.0 8.7": ["otro"], "16.7 4.3 8.6": ["cris"], "11.2 3.9 0.4": ["colorimeter"], "0.2 4.7 3.6": ["servicable"], "-2.7 11.2 8.1": ["keyframe"], "-4.7 6.7 7.8": ["baptist"], "9.3 15.2 -4.1": ["thathe"], "10.7 5.1 13.3": ["bandaids"], "-1.3 4.3 16.5": ["rtf"], "5.8 6.5 16.8": ["fussiest"], "-3.3 -5.1 4.7": ["salsalate"], "-1.4 -1.8 -2.6": ["redeliver"], "5.4 3.1 6.5": ["sheeter"], "-7.1 10.2 13.4": ["cedents"], "-1.4 7.6 19.5": ["remisiers"], "6.2 -0.1 0.9": ["mellophone"], "27.6 8.7 20.3": ["taipan"], "4.0 8.6 10.9": ["autoclaving"], "0.6 7.0 14.8": ["iftars"], "3.6 8.7 10.6": ["swayamvar"], "14.1 2.1 9.4": ["tne"], "8.0 24.3 11.4": ["civilise"], "-3.2 4.5 9.6": ["aligner"], "-9.9 -0.1 7.5": ["preformance"], "13.9 13.1 -9.1": ["rebadge"], "11.2 4.7 11.2": ["writeback"], "-1.9 7.1 -2.3": ["pti"], "8.5 4.1 3.8": ["clamours"], "-4.1 3.9 15.4": ["bago"], "-1.7 9.8 10.2": ["antiangiogenic"], "0.9 2.6 4.3": ["mannose"], "7.8 17.1 6.7": ["basicly"], "5.1 5.6 0.5": ["dg"], "5.7 21.1 21.6": ["windage"], "18.7 7.4 15.6": ["alice"], "7.3 12.6 9.9": ["vamos"], "4.2 -3.4 4.6": ["stairlifts"], "0.8 19.9 7.8": ["evidentially"], "0.8 9.3 18.1": ["rivered"], "8.7 17.1 8.2": ["numpty"], "1.5 8.3 18.2": ["paani"], "10.3 8.5 12.3": ["souqs"], "6.4 16.5 7.8": ["oxidising"], "17.4 11.1 10.5": ["jockstraps"], "11.0 15.1 14.2": ["melittin"], "11.2 8.0 13.7": ["showplaces"], "-3.7 4.5 6.3": ["intermissionless"], "-1.8 7.7 7.1": ["osseous"], "0.6 17.5 8.1": ["undroppable"], "12.5 22.2 0.7": ["deployer"], "3.6 0.3 6.2": ["feddans"], "3.6 7.8 8.2": ["anticlimatic"], "-1.2 17.0 3.5": ["misconfigurations"], "13.9 0.5 9.9": ["wavelike"], "17.5 11.2 22.3": ["protuberances"], "7.9 5.9 15.3": ["brightwork"], "3.2 10.4 7.8": ["datapoint"], "1.6 5.5 4.0": ["wsa"], "6.2 23.1 5.1": ["bretheren"], "2.6 10.2 10.6": ["backstrokers"], "8.3 19.9 10.2": ["vainglory"], "1.8 -0.9 10.2": ["tif"], "-2.1 8.2 8.9": ["famotidine"], "2.5 12.9 7.5": ["topdressing"], "0.4 -1.0 6.5": ["uridine"], "7.4 10.4 10.1": ["interneurons"], "5.2 10.9 11.3": ["nympho"], "14.6 16.0 8.3": ["impersonality"], "7.4 4.1 11.3": ["costa"], "-1.2 10.4 7.8": ["voicework"], "12.5 1.7 11.2": ["reuseable"], "4.3 9.0 25.5": ["rata"], "7.7 14.5 8.5": ["airlocks"], "8.0 30.8 9.0": ["communalists"], "5.2 3.4 -1.8": ["copyists"], "-9.3 7.7 -4.9": ["dealth"], "4.1 21.7 8.5": ["ballhawking"], "15.6 15.4 1.4": ["geocentric"], "32.4 8.5 3.9": ["tickertape"], "8.8 16.7 7.9": ["viceroys"], "1.4 17.9 13.1": ["sullenness"], "3.1 -3.9 15.8": ["friskier"], "7.4 4.2 11.1": ["muchos"], "4.0 18.2 19.4": ["cottager"], "4.6 15.9 13.9": ["overemotional"], "3.3 27.5 10.9": ["sinhalese"], "13.3 3.7 6.2": ["seraphim"], "1.4 4.5 31.7": ["saucing"], "7.5 4.8 5.4": ["fashionability"], "0.2 7.1 12.1": ["tourny"], "4.8 3.6 2.3": ["managership"], "15.7 10.5 10.1": ["radomes"], "14.1 16.2 12.5": ["ringfencing"], "3.8 16.1 15.5": ["propertied"], "14.4 7.5 27.3": ["scow"], "10.4 11.0 23.7": ["ceanothus"], "7.3 6.9 9.9": ["shinkansen"], "7.3 4.6 8.9": ["drachmas"], "13.7 18.6 9.6": ["insolently"], "10.8 12.8 14.9": ["absentminded"], "13.2 18.7 7.0": ["scrooges"], "6.1 2.0 6.0": ["spintronic"], "-5.6 13.6 9.1": ["escapeway"], "13.9 5.5 15.7": ["vaquero"], "9.1 13.2 3.8": ["suceeded"], "2.9 -1.5 6.5": ["prefund"], "3.2 5.6 12.9": ["dvr"], "-0.8 7.7 12.7": ["overcorrection"], "14.1 11.7 8.9": ["spiv"], "-2.6 10.7 -1.7": ["quantitate"], "11.6 1.6 3.6": ["ub"], "12.7 19.4 13.5": ["pulverization"], "11.5 14.0 8.5": ["strategizes"], "4.5 11.9 11.8": ["intertitles"], "-1.4 11.6 2.2": ["goserelin"], "29.5 5.6 19.9": ["coathanger"], "7.4 13.3 12.3": ["astir"], "5.4 -0.7 3.4": ["vodcasts"], "14.1 5.1 7.2": ["biomimetics"], "2.5 5.2 10.0": ["microbuses"], "3.0 2.1 8.6": ["upsells"], "10.9 13.6 7.2": ["pleadingly"], "12.5 -5.1 6.4": ["koruny"], "3.7 7.4 6.9": ["microcars", "routinized"], "8.4 27.8 6.6": ["manoeuver"], "-4.3 7.9 15.0": ["culinarians"], "12.5 24.4 4.6": ["bogy"], "5.0 -2.6 8.6": ["unstamped"], "-2.7 12.3 -2.4": ["endevour"], "3.1 1.6 12.1": ["roberts"], "8.7 11.6 34.3": ["moorhens"], "-4.7 15.4 4.7": ["nonlinearity"], "15.0 7.9 16.6": ["pinions"], "5.8 8.3 2.2": ["exhibitionistic"], "5.2 16.2 6.0": ["misdirects"], "12.1 7.0 7.7": ["palmrest"], "-5.2 -7.8 8.7": ["studentship"], "9.3 11.9 13.9": ["usurers"], "14.3 14.0 1.6": ["vandalizes"], "15.5 30.0 3.7": ["expansionists"], "3.0 5.1 23.8": ["pipfruit"], "8.7 7.5 12.8": ["regionclick"], "3.8 15.6 -0.0": ["dispite"], "2.9 6.8 15.2": ["oro"], "-7.3 4.0 0.1": ["countersign"], "17.1 12.2 21.7": ["townfolk"], "-1.0 6.1 5.9": ["presort"], "-2.3 5.0 6.6": ["rateable"], "1.7 14.9 35.1": ["overwintered"], "10.8 9.2 26.5": ["frijoles"], "11.6 4.9 17.3": ["greasier"], "15.8 6.8 16.5": ["hoofprints"], "9.9 11.6 13.8": ["desis"], "14.0 12.0 11.5": ["eleventy"], "-0.5 26.3 3.8": ["irredentism"], "4.0 6.8 5.1": ["compositors"], "2.2 9.0 12.0": ["papillomavirus"], "7.4 8.9 33.1": ["puds"], "1.8 13.2 10.5": ["overpoweringly"], "-10.6 4.5 1.4": ["episiotomies"], "8.0 22.1 10.0": ["manuevers"], "0.7 6.5 1.8": ["infor"], "0.5 8.5 6.9": ["nailers"], "3.9 9.8 3.2": ["ternary"], "8.2 0.8 8.1": ["depuis"], "11.7 5.5 19.9": ["basset"], "5.0 7.6 4.6": ["nontax"], "11.4 32.6 1.4": ["islamists"], "-0.4 8.3 4.1": ["haled"], "5.3 10.7 -1.2": ["reengaged"], "-11.6 5.7 2.2": ["officership"], "-0.5 12.4 9.8": ["relativities"], "11.5 13.2 19.5": ["splogs"], "-5.7 9.6 2.5": ["amodiaquine"], "-2.4 6.4 3.7": ["doxylamine"], "7.6 18.2 9.1": ["irremediably"], "16.7 3.5 18.6": ["cinnabar"], "-1.5 10.4 -0.1": ["abe"], "19.7 3.5 26.6": ["geode"], "-10.9 10.2 1.1": ["averment"], "28.1 4.0 31.1": ["tiddlers"], "3.5 13.5 15.8": ["puppyhood"], "-1.5 18.1 3.1": ["incrementalist"], "9.6 7.8 2.5": ["shopworkers"], "9.6 16.9 4.0": ["minuteman"], "3.9 9.3 9.0": ["nanoclusters"], "6.3 2.1 6.8": ["sliproad"], "10.1 4.7 30.4": ["bocconcini"], "4.5 19.6 3.6": ["catarrh"], "4.2 3.9 13.7": ["delicates"], "15.2 -3.5 1.5": ["giveway"], "8.1 14.6 7.9": ["compensator"], "13.5 21.5 2.6": ["inextinguishable"], "11.9 -1.9 1.7": ["internation"], "8.7 12.6 7.0": ["wahala"], "-3.2 5.4 9.3": ["tourament"], "6.1 9.2 9.7": ["nobel"], "15.2 4.1 24.7": ["threadlike"], "-6.3 2.9 15.9": ["guarseed"], "0.7 12.3 5.6": ["dewpoints"], "0.9 8.6 -2.8": ["dedicatory"], "16.4 13.4 6.8": ["stamper"], "0.8 11.5 7.1": ["promotionally"], "6.5 -1.1 14.3": ["multiweek"], "-0.8 12.9 17.9": ["coccidiosis"], "7.1 9.3 27.4": ["curlews"], "11.5 -4.2 16.8": ["pinafores"], "1.0 6.9 1.7": ["nuture"], "7.2 6.0 11.7": ["dumpings"], "-2.7 4.1 16.7": ["ros"], "15.3 0.0 7.5": ["biodegradeable"], "9.7 14.3 39.5": ["cordgrass"], "10.5 14.7 13.8": ["participle"], "-1.4 2.5 18.6": ["taels"], "4.3 9.5 3.6": ["haltime"], "6.3 10.0 3.8": ["multitasked"], "2.3 2.3 16.1": ["numismatists"], "1.0 36.3 14.7": ["gametype"], "1.7 12.2 8.9": ["passanger"], "13.5 1.6 18.7": ["gargled"], "-1.5 8.0 11.1": ["lech"], "10.3 17.0 21.1": ["taxonomist"], "0.9 13.0 19.2": ["lactobacilli"], "3.1 3.2 0.1": ["epub"], "3.3 8.4 4.4": ["concretisation"], "6.2 4.0 -0.9": ["divsion"], "12.7 14.0 4.4": ["bulkiest"], "2.6 18.8 9.7": ["lieing"], "10.1 15.8 7.5": ["caterwaul"], "17.4 11.5 17.3": ["crossbeams"], "6.8 1.1 15.0": ["zona"], "7.2 -0.3 6.2": ["dengan"], "-0.7 23.7 4.7": ["projective"], "-4.3 1.2 6.4": ["saxist"], "14.2 7.7 9.5": ["shinned"], "6.1 4.9 27.7": ["hydroponically"], "-5.2 5.2 10.9": ["cathelicidin"], "-9.6 4.7 1.7": ["nonlegal"], "8.2 9.8 11.4": ["structuralism"], "-8.2 5.3 5.7": ["assts"], "0.1 0.5 24.5": ["wharfage"], "4.8 12.8 8.0": ["anyting"], "1.8 4.0 12.4": ["phytoestrogen"], "5.9 -1.4 5.5": ["completive"], "11.3 14.9 17.0": ["shaka"], "9.2 12.2 1.2": ["ransacks"], "-10.3 14.2 -2.1": ["bianet"], "7.1 5.4 15.1": ["shotcrete"], "2.8 5.5 9.2": ["trattorias"], "11.7 3.6 13.6": ["ungraceful"], "-2.2 3.9 4.0": ["nonhybrid"], "9.4 17.5 4.2": ["muteness"], "11.0 7.5 25.9": ["stodge"], "10.1 8.6 12.4": ["kabbadi"], "-3.9 -2.5 4.6": ["eligable"], "-0.8 -0.6 10.7": ["propery"], "9.9 7.5 4.6": ["groovier"], "6.9 21.1 15.3": ["winchman"], "-2.1 -1.4 0.3": ["nationale"], "6.2 26.5 6.2": ["thenceforth"], "1.7 20.2 1.8": ["vulnerably"], "10.3 1.0 1.4": ["noninfringement"], "2.2 6.1 7.9": ["involed"], "11.6 25.4 7.7": ["germans"], "10.4 14.6 9.0": ["glissando"], "15.1 -2.3 13.8": ["alimentary"], "0.7 29.5 1.5": ["belittlement"], "3.1 14.4 14.8": ["trellising"], "8.1 22.0 11.2": ["touchiness"], "6.5 1.6 1.5": ["multistakeholder"], "15.6 13.5 12.6": ["wanly"], "-2.3 14.3 8.2": ["elopes"], "4.5 5.0 26.8": ["puto"], "-3.5 4.5 19.2": ["craveable"], "-8.2 5.9 4.9": ["carryforward"], "11.3 0.9 2.1": ["artspace"], "0.9 5.1 23.2": ["laddoos"], "-4.1 -1.5 10.7": ["defectivity"], "12.2 -9.0 11.9": ["tures"], "7.1 16.9 11.4": ["superwomen"], "17.8 16.9 12.5": ["hyperspeed"], "-1.6 -10.7 1.4": ["cluded"], "9.6 9.6 12.2": ["geophone"], "10.8 2.5 5.8": ["obamas"], "0.5 9.1 11.8": ["kare"], "-9.0 7.4 -0.1": ["canidates"], "5.6 -1.8 8.2": ["tricity"], "1.7 0.1 10.8": ["ghal"], "7.1 16.0 12.8": ["glancingly"], "1.0 4.9 12.4": ["beng"], "14.1 4.3 24.1": ["tarantella"], "12.9 7.4 13.3": ["gearstick"], "0.7 4.9 8.9": ["matricula"], "7.7 7.7 13.1": ["yeong"], "-6.0 9.7 2.5": ["chlorambucil"], "0.7 20.6 8.2": ["enflaming"], "26.6 9.1 13.1": ["chessboards"], "2.4 10.7 13.2": ["ebonics"], "-6.7 -5.2 2.7": ["rescored"], "20.2 8.4 7.3": ["corporatewide"], "3.4 4.3 12.9": ["philatelist"], "6.2 11.6 6.8": ["nonstory"], "15.3 1.2 25.7": ["liquidy"], "15.9 0.4 18.1": ["eck"], "-2.4 24.8 1.0": ["mollycoddle"], "-0.6 1.6 4.3": ["parameterization"], "11.9 18.6 11.3": ["temptresses"], "20.4 13.4 13.7": ["chaebols"], "-1.2 4.6 6.7": ["pitside"], "3.8 7.0 12.4": ["abras"], "0.6 16.8 22.4": ["steersman"], "23.4 1.1 4.7": ["carrousel"], "-3.7 0.6 0.2": ["olf"], "13.0 13.6 10.2": ["pilfers"], "6.4 1.8 12.3": ["sealable"], "-2.5 -5.9 13.7": ["restudy"], "15.4 -1.4 9.6": ["ehf"], "-2.4 1.6 10.5": ["cocreator"], "3.9 5.2 4.9": ["polymerized"], "5.3 5.4 9.3": ["microwatts"], "7.9 4.7 7.8": ["cryptozoology"], "12.2 15.8 12.1": ["hoariest"], "2.2 12.6 5.3": ["biocontainment"], "2.1 15.1 1.3": ["suporters"], "-1.9 8.6 13.2": ["mumbly"], "1.8 4.2 -3.8": ["electromobility"], "8.1 6.1 3.7": ["outslugs"], "2.1 7.9 22.2": ["renourish"], "4.0 14.7 6.4": ["autocratically"], "8.4 -3.2 21.0": ["yogourt"], "8.3 13.2 8.1": ["bastardizing"], "-4.4 6.2 16.2": ["redistributions"], "1.0 20.4 4.8": ["compromisers"], "16.6 8.2 2.3": ["invesment"], "10.2 20.8 13.9": ["bandoliers"], "9.9 9.0 7.8": ["boson"], "4.1 23.4 7.2": ["outcoach"], "8.0 6.8 25.3": ["beadboard"], "18.3 1.7 13.2": ["sweetshop"], "-1.7 14.3 8.9": ["melioidosis"], "-5.3 3.5 14.6": ["revotes"], "-2.0 8.8 0.9": ["lienholders"], "6.6 11.2 11.6": ["electrochemically"], "7.7 19.2 8.1": ["motiveless"], "9.7 4.9 11.4": ["wiggy"], "0.4 -0.9 11.3": ["mcd"], "-0.2 11.6 32.7": ["liveaboards"], "11.1 1.9 15.3": ["inkwells"], "-5.2 9.8 3.4": ["nakas"], "0.1 6.5 10.3": ["homebrewer"], "12.2 19.2 11.9": ["vulgarian"], "10.0 22.9 30.1": ["blackflies"], "6.0 17.1 13.3": ["gooners"], "-6.2 9.5 -5.1": ["flydubaiflydubai"], "2.9 22.5 3.8": ["circumscribing"], "4.0 3.3 18.5": ["hanok"], "7.1 13.5 0.7": ["disharmonious"], "4.3 5.9 10.9": ["geneology"], "6.8 10.6 26.2": ["chine"], "5.1 12.1 10.1": ["adiabatic"], "18.8 12.4 16.1": ["corkscrewed"], "13.1 21.5 23.8": ["scallywag"], "-2.2 2.9 5.7": ["ippr"], "-7.1 5.8 0.8": ["shorstop"], "10.1 6.8 5.6": ["interministerial"], "-6.8 19.5 6.4": ["reelections"], "1.5 6.9 9.7": ["hybridity"], "-1.1 16.1 10.7": ["autonomist"], "6.3 6.1 13.4": ["kc"], "-1.2 2.8 23.9": ["winegrape"], "6.8 -2.8 14.1": ["dk"], "16.2 12.3 21.3": ["beatles"], "2.5 24.8 5.5": ["delusionary"], "6.3 7.3 16.5": ["freegan"], "14.5 -1.1 8.8": ["pvc"], "-1.3 9.9 11.8": ["virions"], "7.9 9.4 15.5": ["goingto"], "-0.7 16.3 10.8": ["worldy"], "-9.6 6.2 1.8": ["intravesical"], "4.4 8.3 15.5": ["clinkers"], "-8.9 10.8 1.3": ["misperceive"], "9.6 6.8 3.4": ["underwhelms"], "9.4 5.2 10.0": ["pitchforked"], "15.3 5.6 15.1": ["wonga"], "10.6 6.9 18.0": ["casement"], "2.1 23.9 2.4": ["guardroom"], "11.3 4.6 20.4": ["filamentous"], "3.9 18.1 15.1": ["cerebrally"], "-6.8 7.1 4.8": ["summative"], "9.7 -0.1 1.9": ["rerated"], "19.1 2.6 6.0": ["beyondbrics"], "2.1 23.1 22.1": ["armyworm"], "0.3 18.2 15.2": ["mycobacterium"], "-4.9 1.7 7.1": ["nonblack"], "8.1 5.2 7.1": ["wallboards"], "9.2 1.9 18.7": ["wavelets"], "-5.5 4.1 22.6": ["wahine"], "8.5 10.5 17.1": ["ricky"], "4.6 3.5 21.3": ["kau"], "15.3 9.1 1.3": ["striked"], "1.2 13.8 5.4": ["mediumship"], "32.6 7.0 18.2": ["honkin"], "0.8 13.7 11.6": ["nones"], "-8.8 6.6 3.4": ["endoscopist"], "5.2 12.2 7.0": ["boolean"], "3.8 7.2 21.4": ["megaquake"], "-3.7 7.0 6.0": ["transparence"], "-3.0 9.4 8.4": ["atobe"], "17.0 -1.1 38.9": ["souse"], "-2.7 -0.3 5.0": ["proceedure"], "-4.7 11.5 -0.1": ["counrty"], "10.3 0.6 25.5": ["feijoada"], "0.5 0.2 6.3": ["mone"], "8.8 5.1 13.2": ["pottered", "reilly"], "2.6 21.7 12.9": ["unremembered"], "20.6 6.3 11.1": ["starchitect"], "-2.6 9.4 3.2": ["pressingly"], "5.6 14.3 0.4": ["synergizing"], "-0.2 21.3 12.5": ["overswing"], "6.1 16.0 10.7": ["prickling"], "-0.2 14.1 3.9": ["bala"], "20.4 18.4 7.5": ["ontop"], "-9.9 14.3 1.7": ["daven"], "16.2 31.7 22.8": ["sandflies"], "2.4 7.8 26.7": ["proteas"], "12.3 10.9 28.2": ["nage"], "-1.4 5.5 1.9": ["vibed"], "-2.2 10.2 8.7": ["cholangiocarcinoma", "sath"], "20.7 12.4 13.5": ["chappie"], "16.3 9.2 22.8": ["multidecade"], "3.4 9.0 -1.4": ["standardbearer"], "-4.9 -6.3 6.0": ["prepubertal"], "3.0 -0.5 11.8": ["aming"], "6.7 11.7 9.0": ["inrushing"], "13.3 8.5 14.7": ["headframe"], "11.2 11.4 8.1": ["skerrick"], "9.3 3.6 39.3": ["guanciale"], "12.7 8.1 25.9": ["bathymetric"], "15.7 18.6 14.6": ["durn"], "8.9 13.1 21.9": ["portaging"], "14.3 0.1 -2.8": ["kgm"], "-6.5 10.1 9.4": ["scoreable"], "1.6 9.8 12.8": ["verismo"], "18.3 12.2 29.9": ["grunter"], "12.4 4.7 3.3": ["officiator"], "12.4 19.1 23.1": ["shwarma"], "3.9 -3.1 -3.3": ["represenatives"], "4.9 15.4 17.3": ["muddiest"], "7.7 -1.4 11.2": ["bindles"], "24.6 6.6 11.1": ["endcap"], "3.4 17.2 8.7": ["zzzz"], "3.9 18.5 16.3": ["troopship"], "18.4 7.5 16.7": ["luxuriantly"], "-3.1 9.8 4.8": ["bleomycin"], "1.1 10.5 -1.6": ["patronises"], "-4.8 2.5 2.7": ["glitazones"], "21.0 9.3 7.3": ["outisde"], "13.0 3.7 19.4": ["jarrah", "antipollution"], "0.2 24.3 0.2": ["faught"], "-2.0 17.0 9.0": ["nuclearisation"], "14.1 12.4 10.7": ["grumped"], "1.1 8.7 19.1": ["garcia"], "-6.7 -0.8 6.4": ["recomendations"], "13.8 14.7 5.2": ["hypotenuse"], "4.4 0.3 10.1": ["handcycling"], "2.8 7.9 11.8": ["cyanosis"], "-7.4 -0.4 -1.9": ["rehabiliation"], "17.9 11.9 21.3": ["wonderlands"], "2.3 6.1 21.7": ["barleywine"], "7.2 11.8 15.6": ["spazz"], "6.5 24.6 17.0": ["egalitarians"], "4.7 12.0 11.1": ["trypsin"], "4.3 10.6 3.0": ["squirreled"], "8.7 8.8 13.5": ["sere"], "0.4 9.4 -2.3": ["therfore"], "4.9 19.1 9.8": ["ballhawks"], "3.3 3.0 18.0": ["jubilees"], "-3.1 12.4 1.6": ["arrrested"], "15.6 6.9 0.1": ["emp"], "2.1 6.0 11.6": ["weathercasters"], "5.2 2.3 -1.7": ["micropower"], "19.9 11.9 16.7": ["streetlamp"], "-4.2 2.1 -1.6": ["informaton"], "2.5 8.1 10.4": ["yeild"], "0.8 12.9 0.9": ["unnoted"], "3.5 -0.7 11.0": ["kwanza"], "-0.4 3.2 8.1": ["iliac"], "6.6 4.8 8.8": ["dieser"], "-3.6 -3.0 8.4": ["rh"], "-1.0 6.9 16.7": ["pinotage"], "0.7 6.5 16.8": ["bahay"], "-3.1 2.6 4.1": ["overpraised"], "18.6 4.1 5.0": ["cushiest"], "9.6 17.9 11.4": ["unscratched"], "-2.8 9.7 7.9": ["haplogroup"], "13.1 8.7 8.3": ["unlevel"], "-4.8 14.1 1.6": ["polytrauma"], "0.8 5.0 8.8": ["deodorized"], "7.3 5.6 0.6": ["courtoom"], "22.3 21.5 21.4": ["blowgun"], "-0.1 8.4 31.2": ["aji"], "7.8 7.7 5.9": ["tomahawked"], "4.1 9.1 16.0": ["croppers"], "3.0 16.3 2.0": ["cordoning"], "6.0 20.3 7.1": ["sunder"], "8.0 -2.9 18.2": ["ladyboys"], "-6.5 14.8 6.8": ["predeployment"], "3.8 21.2 1.4": ["analogical"], "1.8 -0.7 11.3": ["churidars"], "6.4 3.4 21.1": ["strudels"], "28.4 7.6 4.5": ["takover"], "0.9 9.0 12.5": ["sackers"], "-0.3 7.3 11.3": ["mujra"], "-3.6 9.1 6.5": ["ususal"], "6.9 35.4 -3.0": ["reconnoitering"], "-3.4 17.1 14.8": ["passover"], "-0.9 12.1 11.8": ["overprepared"], "7.4 13.6 4.5": ["shadiness"], "7.6 4.7 12.4": ["minibikes"], "10.8 5.3 6.4": ["dirndls"], "-0.4 8.4 -0.6": ["graphology"], "3.2 10.4 15.1": ["yaya"], "-2.5 8.3 5.0": ["monotherapies"], "9.1 8.6 14.0": ["droptop"], "-0.8 -2.4 4.2": ["alloting"], "-1.9 3.5 12.7": ["tocopherols"], "10.6 9.4 12.6": ["eldery"], "-1.5 27.2 9.9": ["sinhala"], "20.6 16.7 14.8": ["phobics"], "6.4 11.0 11.8": ["hutment"], "14.2 -1.5 1.6": ["stirling"], "11.5 12.4 10.7": ["slickster"], "7.3 9.6 8.0": ["resuce"], "10.4 4.8 7.7": ["tarrif"], "6.4 1.9 5.8": ["estos"], "5.9 7.8 -0.5": ["gallivant"], "8.5 13.8 14.6": ["nelly"], "-0.2 2.1 3.8": ["procedings"], "1.9 2.5 13.9": ["winkers"], "-4.8 6.9 4.4": ["glbt"], "7.0 -2.2 -1.3": ["currenty"], "-0.0 19.9 6.1": ["evolutionism"], "9.1 9.7 21.6": ["jitterbugs"], "11.5 16.4 15.2": ["keffiyehs"], "19.2 22.0 11.3": ["greenmail"], "14.0 7.4 0.4": ["proprietory"], "17.2 15.2 27.1": ["pliosaur"], "-3.2 0.6 17.4": ["roi"], "18.0 2.3 38.2": ["shuckers"], "19.3 13.1 8.8": ["plonks"], "7.3 2.7 3.0": ["astrologists"], "15.4 8.7 23.2": ["sawbuck"], "12.8 7.7 11.5": ["anno"], "9.3 19.6 12.5": ["goeth"], "-0.9 11.2 16.7": ["rebloom"], "-0.2 18.2 6.4": ["credibilty"], "-1.2 16.6 7.1": ["calibres"], "2.1 7.1 -0.4": ["discoursing"], "12.7 15.8 8.0": ["roundel"], "-7.2 14.3 10.0": ["reteach"], "-0.0 6.3 14.2": ["patka", "monolaurin"], "1.4 10.0 9.8": ["nephritis"], "5.9 3.4 13.3": ["retaped"], "-1.8 3.2 3.4": ["jcpenney"], "13.5 7.5 8.8": ["hearthrob"], "0.0 6.0 15.0": ["memcached"], "7.5 8.9 31.8": ["semifreddo"], "5.0 -2.5 7.8": ["urethanes"], "6.4 5.5 6.1": ["thermogenesis"], "-7.1 7.4 1.5": ["decompensation"], "10.9 25.8 5.6": ["perniciously"], "10.3 18.9 6.7": ["antimilitary"], "11.3 7.7 7.9": ["transferal"], "18.0 2.3 6.7": ["illion"], "-4.5 -0.7 10.9": ["jackscrew"], "15.6 1.6 -3.2": ["compa"], "14.6 13.5 9.0": ["cacophonic"], "12.4 9.1 12.8": ["calorimeter"], "17.6 15.8 12.0": ["boxart"], "-2.9 20.7 7.4": ["disambiguation"], "-3.2 3.8 4.6": ["neurophysiologist"], "2.5 14.5 8.9": ["overscan"], "6.4 21.6 5.5": ["oversensitivity"], "9.8 -5.2 16.1": ["restaraunt"], "22.5 -9.1 -2.8": ["cente"], "17.1 3.8 16.4": ["dayslong"], "13.5 12.6 15.3": ["tiredly"], "11.8 -0.3 7.7": ["thanexpected"], "2.4 7.7 14.8": ["homologs"], "5.1 17.5 1.2": ["villainized"], "5.4 12.9 18.5": ["hickeys"], "-1.7 1.1 9.1": ["nondrug"], "5.7 2.3 15.7": ["milwaukee"], "-8.0 9.2 4.3": ["criterions"], "-0.8 13.8 1.2": ["fluoroscopic"], "4.5 9.5 8.1": ["abstractionist"], "-0.5 2.2 7.0": ["coachloads"], "16.0 22.5 20.6": ["hunkering"], "-2.2 6.5 19.1": ["tapu"], "2.8 21.5 8.9": ["unfortified"], "15.3 7.0 23.2": ["sifters"], "-1.6 10.1 -0.3": ["cornerkick"], "11.3 16.3 12.6": ["heavenwards", "squirmingly"], "-5.1 14.1 1.8": ["deselecting"], "10.0 9.1 10.5": ["aristo"], "26.0 7.1 22.9": ["twirly"], "12.1 9.9 24.4": ["hydrofoils"], "1.5 0.2 9.5": ["recumbents"], "4.0 15.9 11.6": ["defensins"], "-2.8 11.4 13.4": ["eutectic"], "10.7 9.4 7.0": ["rebase"], "14.4 8.6 21.8": ["bombe"], "7.3 14.8 14.9": ["moorlands"], "-6.1 14.1 -0.7": ["corespondent"], "-1.0 6.3 10.0": ["flexor"], "-1.0 13.3 6.7": ["hejab"], "3.7 -1.6 -1.1": ["valuated"], "4.5 16.1 10.2": ["unburnt"], "1.0 3.3 -1.4": ["namechecked"], "4.4 12.7 4.9": ["mobike"], "17.7 0.0 1.8": ["wordt"], "5.6 4.5 26.3": ["criollo"], "16.2 16.8 16.4": ["yobbos"], "-3.1 15.9 11.8": ["childfree"], "4.0 9.3 -8.5": ["effecient"], "11.5 7.9 12.4": ["glissandos"], "15.0 19.5 23.2": ["horseflies"], "5.5 7.6 18.6": ["bara"], "5.2 6.0 7.0": ["bellringers"], "-3.3 9.3 0.5": ["caoch"], "6.9 7.7 31.4": ["compotes"], "21.3 8.7 -0.0": ["renationalise"], "2.8 13.5 10.3": ["deorbit"], "10.9 4.8 31.4": ["smokehouses"], "4.5 11.9 6.2": ["artical"], "8.5 -0.6 -2.4": ["dealed"], "26.6 8.3 5.0": ["blazoned"], "13.2 8.4 13.3": ["carollers"], "1.1 4.3 7.4": ["isometrics"], "3.3 19.1 20.0": ["undescribed"], "3.2 16.6 14.2": ["agglomerates"], "10.8 12.8 7.1": ["bedmates"], "9.8 9.2 11.6": ["trainspotters"], "10.0 2.5 1.4": ["lastweek"], "12.6 4.1 21.3": ["bottlebrush"], "5.4 14.2 6.4": ["baselining"], "0.1 21.5 5.6": ["reconciler"], "21.1 8.8 5.4": ["snazziest"], "1.6 -1.0 11.4": ["whoonga"], "9.6 0.9 16.2": ["rustier"], "7.6 14.4 7.4": ["underhandedly"], "-4.2 3.2 1.9": ["ihr"], "-0.1 4.9 15.9": ["quaffable"], "-8.0 5.3 5.1": ["progranulin"], "0.7 12.3 5.0": ["inconsistant"], "10.7 13.4 2.8": ["diviner"], "1.1 17.0 8.5": ["unflappably"], "11.6 12.9 4.9": ["ffs"], "0.1 23.8 14.5": ["blessedness"], "8.2 6.6 7.9": ["skive"], "-2.0 13.7 2.5": ["covenantal"], "11.1 4.1 8.9": ["minimills"], "11.3 5.8 20.7": ["mulcher"], "0.9 21.9 2.8": ["rhetorician"], "15.7 11.9 12.8": ["futz"], "0.5 5.4 1.8": ["internationality"], "5.7 8.8 20.1": ["lolo"], "19.9 16.6 26.9": ["snouted"], "3.4 13.0 7.0": ["directivity"], "8.5 0.8 5.1": ["ktpa"], "27.5 21.7 8.4": ["whirrs"], "-3.3 7.5 2.7": ["opthalmologist"], "6.9 -2.3 6.5": ["onethird"], "6.9 2.3 10.0": ["cumbias"], "8.0 -1.9 16.6": ["panama"], "11.8 13.9 7.9": ["unproductively"], "-1.3 1.6 4.4": ["conservatoire"], "24.1 12.1 15.4": ["sandpits"], "9.0 1.3 9.0": ["edocs"], "-3.7 15.9 8.7": ["mitzvahs"], "8.0 12.7 16.7": ["unutterably"], "5.4 11.9 19.9": ["bushcraft"], "10.6 24.5 25.8": ["vining"], "16.6 9.1 10.6": ["derisk"], "6.2 10.9 9.1": ["jailtime"], "1.0 -5.4 12.8": ["betaine"], "9.8 18.9 13.6": ["indebt"], "19.3 14.7 9.7": ["daftest"], "-8.1 -1.2 3.4": ["expe"], "6.4 10.4 2.7": ["mahant"], "1.5 20.4 11.1": ["empiricist"], "14.0 24.7 4.2": ["soullessness"], "-1.2 15.2 5.8": ["uncontestable"], "-6.5 0.9 1.4": ["sunwear"], "5.6 -0.4 11.7": ["jollier"], "-4.4 6.4 12.3": ["landownership"], "2.1 0.2 2.3": ["reprocessor"], "12.5 13.9 21.5": ["canting"], "19.1 23.7 10.7": ["apocalyptically"], "0.8 -8.0 11.4": ["microbusiness"], "20.3 10.7 7.2": ["renationalization"], "5.0 7.1 6.7": ["remaning"], "1.3 11.1 2.4": ["mopup"], "12.3 21.9 8.4": ["superweeds"], "3.8 8.4 4.4": ["clinged"], "6.8 5.1 -0.4": ["moins"], "6.4 8.2 18.0": ["machi"], "14.1 9.8 7.8": ["eople"], "18.0 17.5 43.3": ["tunicates"], "16.0 10.4 18.0": ["motorheads"], "21.5 19.5 16.9": ["pilferers"], "5.4 8.7 9.4": ["novae"], "8.0 19.4 0.7": ["demobilising"], "6.7 12.4 2.7": ["synergic"], "2.3 5.6 4.2": ["thous"], "3.0 -6.2 9.8": ["andrology"], "17.9 8.8 5.5": ["poises"], "14.4 -0.5 10.1": ["pedestrianise"], "6.4 -0.2 8.2": ["gc"], "-2.8 1.8 10.4": ["pricewise"], "8.4 8.9 29.8": ["piebald"], "-5.4 11.1 3.0": ["titrate"], "6.2 3.4 13.6": ["overshoes"], "5.7 -0.4 18.0": ["huang"], "8.0 11.9 1.1": ["decarbonising"], "14.6 6.8 12.4": ["grassless"], "19.4 7.7 6.2": ["digitals"], "3.6 9.8 11.9": ["folklores"], "-5.0 4.4 4.1": ["qualifing"], "1.1 1.1 8.4": ["birthmothers"], "13.5 15.2 11.6": ["nebulas"], "-2.6 5.9 -0.8": ["estatic"], "9.9 14.8 6.7": ["bashfulness"], "4.5 5.4 2.7": ["hass"], "-1.7 12.6 0.2": ["retyped"], "17.5 10.3 8.7": ["highstreet"], "2.1 5.1 1.5": ["minsiter"], "7.4 13.6 20.9": ["niger"], "-0.8 2.6 12.7": ["cocoas"], "11.4 17.3 18.4": ["slogger"], "21.5 10.6 28.6": ["crocodilian"], "5.5 2.7 11.6": ["topsy"], "-14.3 6.9 8.3": ["agendized"], "9.8 2.5 6.1": ["weer"], "4.3 -4.6 8.0": ["transvaginal"], "6.8 -4.6 7.7": ["raciness"], "-4.1 6.6 0.4": ["achievments"], "9.5 11.3 12.6": ["factorial"], "13.6 12.9 6.0": ["dipshit"], "9.8 8.5 37.5": ["veloute"], "5.5 23.0 1.4": ["secularizing"], "0.0 -2.1 10.5": ["rolloff"], "-4.6 3.8 1.9": ["matriculates"], "-0.4 11.8 10.3": ["spiritualities"], "3.4 11.0 9.1": ["mesosphere"], "5.0 9.0 9.4": ["fabulosity"], "7.3 2.4 21.3": ["chlorella"], "3.2 6.7 7.6": ["homologue"], "6.7 8.6 4.6": ["whiteboarding"], "1.9 6.8 1.3": ["howto"], "-0.3 6.3 3.1": ["topseos"], "-0.5 -1.3 2.1": ["unestablished"], "2.4 5.6 8.8": ["els"], "4.8 8.4 11.9": ["goaltended"], "4.5 2.2 14.3": ["arti"], "2.2 8.9 4.6": ["auth"], "1.9 12.6 11.0": ["backovers"], "12.2 12.9 44.2": ["macks"], "2.5 8.2 2.7": ["cofactors"], "8.2 5.6 -3.5": ["errupted"], "11.4 9.5 25.4": ["surfside"], "14.7 12.9 19.1": ["tailless"], "5.8 3.7 31.3": ["pomelos"], "8.7 13.6 7.1": ["unpretentiously"], "7.6 14.7 21.9": ["anthers"], "5.3 9.4 52.0": ["pomfret"], "22.7 1.9 20.6": ["mahog"], "-0.1 11.5 9.1": ["yuko"], "-5.5 6.4 2.6": ["qualifiying"], "-9.4 0.5 5.6": ["probands"], "-1.1 23.6 2.5": ["seclude"], "-7.7 26.0 5.6": ["unhesitating"], "-7.5 4.8 15.4": ["shoujo"], "7.6 11.1 14.2": ["daftness"], "6.5 9.0 3.3": ["polic"], "-3.7 -5.1 1.8": ["soum"], "1.2 7.3 9.2": ["rubbered"], "13.2 16.0 12.4": ["pageview"], "6.8 -0.2 10.3": ["lrg"], "2.9 20.0 1.8": ["disconcert"], "-4.0 10.7 9.2": ["downzone"], "6.6 8.2 24.9": ["pickiness"], "8.0 6.1 15.8": ["steles"], "-3.9 5.2 1.2": ["coordinative"], "7.6 14.4 7.3": ["devaluate"], "-3.2 13.0 5.2": ["manipur"], "2.8 12.4 -2.3": ["conciliators"], "9.1 24.4 9.0": ["drudging"], "11.0 17.0 24.2": ["snacker"], "3.8 4.5 12.4": ["presider"], "6.0 13.4 13.4": ["gerrrg"], "15.6 13.4 8.6": ["evanescence"], "7.6 1.2 9.6": ["planethood"], "-3.4 13.2 1.0": ["disestablish"], "13.7 12.6 9.5": ["commissionaire"], "2.2 0.4 17.6": ["segs"], "1.6 5.4 17.7": ["chlorinator"], "12.9 7.6 13.8": ["musta"], "25.4 20.2 7.0": ["superstrong"], "7.2 -2.2 -0.7": ["andwill"], "8.1 3.8 -0.3": ["autoroute"], "9.0 3.2 11.1": ["negligees"], "14.9 7.1 13.2": ["ganglia"], "2.5 1.9 11.0": ["richrelevance"], "10.8 17.0 7.7": ["kibitzers"], "3.5 6.5 11.8": ["kanetix"], "6.6 12.2 11.2": ["timewarp"], "4.8 7.8 2.0": ["interparliamentary"], "3.7 1.6 1.3": ["quietening"], "6.5 6.2 15.8": ["hoopers"], "0.9 9.5 8.0": ["stayin"], "13.1 2.3 8.6": ["neoclassic"], "-2.7 2.9 28.6": ["dals"], "1.8 18.0 7.5": ["celerity"], "-7.4 7.6 -2.1": ["abscence"], "2.1 -0.7 9.6": ["babymoon"], "-0.1 7.5 6.0": ["outdistances"], "15.0 -2.1 6.0": ["eez"], "14.8 14.2 2.9": ["vaunting"], "-6.2 -1.6 3.2": ["verballed"], "-4.6 -1.7 -4.9": ["etravirine"], "2.6 5.8 1.3": ["sendoffs"], "9.5 3.1 30.7": ["jujube"], "6.7 -1.1 18.5": ["softgels"], "5.2 8.2 29.4": ["bobolinks"], "11.6 34.7 11.6": ["cylons"], "7.8 -5.9 6.8": ["afternooon"], "17.3 16.2 21.0": ["scullery"], "13.5 19.0 2.0": ["fense"], "10.3 4.2 1.4": ["useability"], "6.5 17.6 19.5": ["dirk"], "5.9 15.6 5.7": ["protectants"], "7.1 8.5 3.2": ["drilldown"], "3.2 1.1 6.2": ["versa"], "17.6 12.0 14.8": ["dingbats"], "5.7 12.4 6.1": ["inflect"], "8.1 14.9 10.4": ["substorm"], "5.0 7.5 4.0": ["soapies"], "-2.7 14.2 11.9": ["worser"], "4.4 16.5 8.2": ["immaturely"], "3.9 13.3 -2.7": ["penpals"], "5.4 13.6 4.7": ["edgeways"], "4.2 4.0 7.3": ["inflamation"], "3.9 29.1 13.8": ["badassery"], "12.7 14.0 14.0": ["spasming"], "-3.3 -4.2 7.8": ["assessement"], "5.7 16.5 6.5": ["stalkerish"], "2.1 -11.7 -0.6": ["aweek"], "-0.7 -10.1 7.0": ["ehs"], "-3.9 4.8 -0.8": ["attornies"], "-4.4 2.9 9.8": ["accordionists"], "5.8 3.6 12.2": ["quatre"], "3.3 4.1 20.6": ["minicasinos"], "12.5 11.0 20.8": ["skivvy"], "2.2 27.3 8.0": ["unreasoned"], "5.6 22.1 -4.4": ["cyberthreat"], "-0.9 11.1 4.8": ["mercied"], "19.1 7.9 24.7": ["marrows"], "-6.7 6.9 12.8": ["nitrification"], "18.1 22.7 5.8": ["tastelessly"], "3.1 14.4 11.2": ["soooooooo"], "-0.9 4.9 4.5": ["coenzyme"], "-10.6 1.7 -2.0": ["roadtrips"], "12.7 15.5 11.0": ["gerontocracy"], "2.1 9.3 1.0": ["camapign"], "-3.0 8.9 14.4": ["resonable"], "18.6 7.7 11.3": ["ballons"], "13.5 7.7 10.2": ["reamer"], "9.8 10.2 14.9": ["poolroom"], "10.5 2.2 6.4": ["cookstove"], "-6.5 1.3 7.5": ["redefault"], "8.3 33.6 11.7": ["shmup"], "11.4 22.4 16.1": ["midship"], "1.7 5.7 4.6": ["maladjustment"], "1.1 19.7 32.0": ["ringnecks"], "12.6 14.1 10.6": ["oldtimer"], "0.7 17.7 -0.7": ["untruthfully"], "15.4 8.8 19.2": ["corpulence"], "0.3 10.6 7.5": ["kettled"], "6.5 4.8 2.8": ["immunochemistry"], "10.3 15.3 15.5": ["yaws"], "10.8 26.6 4.2": ["ennobles"], "8.1 10.5 22.4": ["astilbe"], "6.5 21.9 15.2": ["bodhisattva"], "17.3 12.6 26.0": ["pentas"], "-2.9 10.7 16.9": ["maund"], "2.1 9.0 4.8": ["congruous"], "3.8 15.3 7.0": ["orneriness"], "0.0 1.2 9.6": ["selegiline"], "10.1 16.3 17.1": ["arachnophobia"], "5.7 11.5 15.5": ["vacuoles"], "-7.0 6.2 0.3": ["conjoint"], "5.8 7.8 1.9": ["unclad"], "4.5 8.2 19.8": ["beedis"], "5.0 -5.0 6.8": ["credenzas"], "9.6 4.2 6.3": ["misdated"], "3.3 4.9 -0.2": ["anguishes"], "9.9 4.5 20.8": ["banteng"], "4.3 18.4 9.8": ["entraps"], "6.6 4.0 12.3": ["christina"], "7.1 5.9 4.5": ["dollarised"], "4.8 10.3 10.2": ["unrepairable"], "10.8 14.2 17.6": ["dishrag"], "-4.2 4.2 20.9": ["coastside"], "10.7 -1.6 -2.8": ["sexualising"], "9.3 33.0 19.2": ["frogman"], "-1.3 24.4 4.7": ["braveness"], "3.9 -0.0 16.3": ["silkier"], "5.9 10.1 14.0": ["marg"], "6.2 5.4 5.1": ["welll"], "10.7 11.7 5.3": ["exorcises"], "10.8 3.8 19.0": ["bibulous"], "20.3 24.0 24.6": ["katamari"], "0.4 -2.4 -1.8": ["juh"], "17.5 11.3 27.0": ["moggie"], "-5.6 0.8 5.8": ["odanacatib"], "13.0 -3.9 13.0": ["boucle"], "3.0 10.9 3.5": ["wanding"], "-4.2 12.4 21.7": ["snowmachiners"], "7.8 -3.3 8.6": ["prkg"], "4.6 6.5 7.0": ["gyan"], "-1.4 12.6 -1.5": ["wehave"], "13.5 11.7 17.1": ["baldheaded"], "6.9 11.9 13.8": ["xanthohumol"], "12.1 7.3 10.4": ["duce"], "11.8 10.5 4.5": ["editrix"], "-3.4 10.2 15.0": ["basecoat", "kacha"], "4.0 6.9 6.7": ["hyaluronidases"], "4.5 3.2 6.4": ["thruout"], "3.4 26.8 9.0": ["unregenerate"], "14.6 16.3 23.5": ["meadowlark"], "-3.3 4.1 23.3": ["postharvest"], "-5.3 -1.7 0.8": ["avilable"], "5.7 1.6 4.6": ["disendorsed"], "10.1 27.3 7.3": ["unquiet"], "18.9 5.0 16.0": ["dumptruck"], "7.8 -1.6 0.8": ["insalubrious"], "6.8 6.3 12.4": ["mathletes"], "6.8 20.5 6.8": ["graveness"], "3.9 3.8 17.3": ["dustings"], "13.7 -1.0 21.6": ["tiebacks"], "8.9 25.7 7.7": ["lulz"], "5.8 6.4 11.0": ["saddlecloth"], "10.2 9.1 28.6": ["groyne"], "2.9 0.7 10.2": ["craftswomen"], "8.2 9.3 8.9": ["prolapsed"], "28.3 4.1 2.6": ["spruiker"], "13.0 -1.9 7.6": ["reseachers"], "4.3 1.4 5.0": ["househunting"], "-1.3 -1.5 2.6": ["cabergoline"], "15.6 -4.8 4.3": ["assn"], "2.7 19.7 8.0": ["noncombustible"], "-3.2 8.5 4.3": ["rebreather"], "24.8 18.3 31.5": ["merman"], "3.5 1.7 4.7": ["commisioners"], "7.0 11.2 14.6": ["sunlamps"], "9.0 9.5 1.5": ["protostar"], "1.1 23.6 20.5": ["bluffer"], "10.2 2.4 8.4": ["benfits"], "18.9 13.9 13.8": ["stickman"], "-9.0 16.0 2.6": ["relationally"], "1.8 12.9 7.0": ["adrenergic"], "-2.1 7.1 14.9": ["pyrethrins"], "7.6 0.3 37.0": ["capon"], "5.8 3.2 -1.7": ["niched"], "-1.4 5.5 0.4": ["sorption"], "15.1 6.9 15.5": ["cack"], "5.0 2.8 3.1": ["leakproof"], "1.8 12.8 10.3": ["prodemocracy"], "0.3 12.8 2.0": ["refection"], "9.3 1.5 15.1": ["neckpiece"], "19.3 17.5 9.9": ["meaninglessly"], "16.3 1.6 40.9": ["tobiko"], "2.9 10.6 14.4": ["kum"], "10.9 8.5 6.0": ["unclosed"], "4.4 4.0 14.8": ["radiographically"], "8.1 4.9 4.5": ["narcocorridos"], "9.3 14.8 -1.3": ["telegrapher"], "-6.0 10.1 3.3": ["nonreaders"], "14.7 -0.0 -3.7": ["bunglings"], "12.4 9.1 27.3": ["panicles"], "-3.5 1.4 5.6": ["reconfigurability"], "10.8 6.3 3.9": ["newstand"], "-2.9 5.9 16.5": ["fermentations"], "7.9 10.1 4.0": ["columbus"], "7.0 17.6 25.7": ["halyards"], "-5.0 7.4 10.2": ["azoles"], "15.9 8.8 28.8": ["hawthorns"], "16.9 9.1 7.2": ["kidz"], "-1.4 5.4 5.6": ["noe"], "3.2 14.5 9.7": ["eosinophil"], "-2.7 2.4 4.7": ["electrowinning"], "11.5 21.6 12.9": ["fleetest"], "2.7 5.7 8.1": ["asi"], "6.7 7.0 16.7": ["karatedo"], "12.2 5.1 8.4": ["wanky"], "7.8 7.9 11.0": ["derailleurs"], "-2.1 3.7 9.3": ["collagenase"], "10.9 5.9 38.9": ["garbanzo"], "17.1 21.1 15.2": ["cherubim"], "-0.6 1.2 13.7": ["robinson"], "15.6 -2.0 -0.8": ["pressplay"], "26.4 19.4 30.5": ["eclair"], "7.5 2.0 39.4": ["portobellos"], "14.2 9.0 8.6": ["tattoed"], "4.8 6.7 27.2": ["oleo"], "4.8 1.2 4.1": ["presetting"], "-5.2 9.3 6.1": ["encumbers"], "0.8 7.2 11.0": ["granduncle"], "7.0 -10.2 -1.8": ["forewent"], "4.4 -2.0 12.1": ["lauren"], "-6.6 5.7 10.1": ["betterments"], "7.7 7.2 34.4": ["colcannon"], "9.8 -3.2 7.1": ["questo"], "3.9 1.0 5.2": ["goawebnews"], "1.1 12.6 29.2": ["redpolls"], "6.7 5.2 12.1": ["overpacked"], "7.1 6.8 11.6": ["dahling"], "1.0 6.2 16.8": ["cashout"], "2.6 20.8 8.5": ["nonmovant"], "20.9 8.6 17.3": ["kookaburras"], "7.6 6.5 16.4": ["divey"], "2.9 13.4 13.9": ["aspergillosis"], "4.5 -1.8 6.2": ["aboutus"], "14.5 21.4 7.1": ["bankrollers"], "5.5 -1.8 15.8": ["lambswool"], "7.5 7.2 10.6": ["checksums"], "-3.9 4.0 11.2": ["letterer"], "11.4 20.6 6.0": ["tinderboxes"], "10.0 5.2 13.3": ["caff"], "-1.4 16.1 3.1": ["condem"], "-6.4 1.2 6.9": ["vacatur"], "0.9 11.3 12.1": ["vocalizes"], "-2.7 0.6 6.2": ["novelette"], "-1.5 13.0 4.6": ["authoress"], "21.4 18.7 21.3": ["spheroid"], "8.1 10.3 11.8": ["layback"], "0.7 8.4 10.9": ["tham"], "12.7 5.3 53.4": ["crabcake"], "14.3 4.8 13.6": ["lolls"], "6.6 -7.0 1.1": ["progams"], "8.7 9.2 26.4": ["creamiest"], "-1.1 13.0 4.3": ["etre"], "7.8 5.4 12.4": ["nonindustrial"], "7.8 1.1 8.5": ["urogenital"], "0.9 7.4 7.5": ["arbitrability"], "14.5 17.1 15.7": ["nunchakus"], "7.3 9.7 5.5": ["sweatier"], "3.9 12.0 9.3": ["contentedness"], "10.5 8.8 11.4": ["merriest"], "-4.0 -0.6 15.7": ["visitorship"], "18.5 5.3 -1.0": ["optronics"], "-2.2 2.7 6.6": ["testifiers"], "7.6 5.9 -1.5": ["bookstall"], "-9.9 4.7 6.6": ["vasodilators"], "-1.6 18.2 22.8": ["salination"], "7.5 7.7 10.4": ["nonbiological"], "-3.3 -2.8 9.1": ["bonne"], "7.8 4.7 20.3": ["quadricentennial"], "-8.4 -1.9 4.9": ["pupillage"], "6.6 9.4 4.5": ["bcoz"], "-8.1 2.6 1.2": ["thecurrent"], "12.4 9.4 14.8": ["plectrum"], "6.2 24.0 7.4": ["balkanize"], "3.2 9.5 9.2": ["timeshifting"], "9.5 1.6 5.0": ["nonmetal"], "-10.9 4.5 8.6": ["peformances"], "10.5 9.5 13.7": ["fops"], "7.6 7.8 7.6": ["neroli"], "15.5 6.0 17.2": ["kleenex"], "8.8 14.7 0.8": ["ambivalently"], "18.2 5.3 12.8": ["groupon"], "13.5 3.7 9.7": ["chandeliered"], "4.8 22.4 17.1": ["defoliating"], "-0.1 2.8 12.9": ["subfield"], "16.7 18.9 8.1": ["banditos"], "-6.3 2.3 -0.4": ["responsivity"], "-2.1 5.9 -0.9": ["appssavvy"], "-0.8 -0.4 5.3": ["specifier"], "15.3 12.7 40.0": ["gudgeon"], "-1.7 0.1 7.1": ["nonstructural"], "9.2 3.4 11.1": ["kde"], "1.5 15.4 12.4": ["nasopharynx"], "4.4 18.1 -0.2": ["sorest"], "-7.4 7.3 9.1": ["hypochlorite"], "2.0 11.2 13.0": ["fingerings"], "-2.8 5.8 3.8": ["worldcup"], "3.8 5.9 -0.0": ["flyering"], "10.5 42.8 16.9": ["necromorphs"], "1.4 6.4 -1.9": ["locksets"], "17.9 30.9 9.8": ["jedi"], "2.2 9.6 3.5": ["wieder"], "2.0 5.2 8.0": ["immunofluorescence"], "2.5 0.7 13.0": ["colourants"], "6.4 -3.7 3.6": ["shs"], "13.3 -0.3 17.3": ["pompadours"], "5.1 6.0 6.8": ["noire"], "6.9 7.9 13.1": ["micrometre", "multistop"], "-3.4 12.0 13.4": ["freethrow"], "0.2 12.0 5.9": ["preaseason"], "-1.9 11.2 1.5": ["permittivity"], "-3.7 9.3 10.8": ["penicillins"], "1.5 7.9 8.6": ["uplisting"], "4.7 10.7 4.6": ["bigman"], "7.5 -9.2 6.4": ["mih"], "9.3 2.3 8.3": ["mercedes"], "15.9 9.4 27.3": ["grazer"], "15.6 27.0 9.2": ["incubus"], "12.8 13.0 15.3": ["whiplashed"], "-3.0 0.3 3.0": ["centennials"], "-0.0 25.0 2.3": ["wronging"], "1.1 0.1 2.6": ["faciliate"], "2.0 4.5 26.5": ["calamansi"], "2.9 -3.7 8.7": ["lipodissolve"], "5.6 1.7 -1.9": ["anumber"], "5.9 21.6 6.4": ["insanities"], "6.6 14.6 7.7": ["abortifacients"], "17.8 17.1 5.9": ["bejeebers"], "2.3 2.8 1.4": ["workshare"], "9.3 13.2 -2.4": ["fulsomely"], "-3.1 2.2 15.1": ["tayong"], "7.7 1.0 10.4": ["eyeliners"], "8.6 5.0 6.6": ["peaktime"], "2.3 4.4 6.5": ["dalbavancin"], "8.7 4.7 10.7": ["nevada"], "19.6 4.2 14.9": ["donk"], "9.2 6.0 -2.9": ["boycot"], "6.9 10.2 2.1": ["dilema"], "-0.5 5.7 10.6": ["jg"], "7.9 4.3 15.0": ["shizzle"], "23.4 22.5 23.9": ["maws"], "7.0 0.9 -1.3": ["specualtion"], "18.0 20.3 17.0": ["grav"], "35.2 12.6 29.7": ["tyrannosaurus"], "9.0 7.5 4.8": ["photoblog"], "2.1 1.2 -1.7": ["higer"], "5.9 5.8 12.2": ["hak"], "-0.5 21.7 11.0": ["thematics"], "-4.7 -1.7 10.1": ["langbeinite"], "13.0 -4.8 9.7": ["funnywoman"], "11.6 -2.2 1.2": ["ccd"], "14.9 18.0 16.9": ["nimrods"], "19.8 5.2 8.9": ["menage"], "11.9 19.9 7.0": ["atomically"], "4.9 15.2 14.1": ["funnybone"], "-1.8 1.8 10.3": ["fp"], "-0.8 14.9 7.5": ["unvented"], "12.7 7.9 15.3": ["congo"], "6.9 21.0 7.2": ["antiunion"], "7.8 5.1 8.4": ["coronaries"], "10.4 20.0 29.8": ["laydowns"], "13.8 10.8 15.7": ["puckstopper"], "-4.3 15.7 8.0": ["impedances"], "12.6 16.6 19.3": ["meself"], "2.5 8.2 13.7": ["snarked"], "-1.0 12.9 1.5": ["vicitm"], "-4.1 6.8 3.5": ["convalesced"], "8.0 5.0 2.4": ["mutualisation"], "-5.8 5.3 10.0": ["arsenate"], "8.9 7.8 7.5": ["janta"], "20.9 19.0 9.2": ["multistoried"], "2.1 12.0 15.6": ["kenneled"], "7.7 3.5 0.9": ["mation"], "4.2 4.8 26.6": ["sabzi"], "-2.3 13.6 4.5": ["communality"], "13.6 6.6 4.6": ["sitings"], "1.5 -2.1 8.0": ["soli"], "-4.6 16.4 7.4": ["redialing"], "2.1 9.0 10.9": ["greatgrandchildren"], "0.2 1.0 3.5": ["haematologist"], "-0.0 6.5 22.0": ["hari"], "8.1 -2.0 11.5": ["eas"], "-4.3 15.4 4.5": ["occurances"], "8.6 1.2 0.0": ["reconditions"], "4.3 5.2 7.7": ["finical"], "9.7 5.6 15.1": ["dandyish"], "23.5 13.7 10.5": ["smashers"], "11.5 8.4 24.4": ["bougainvilleas"], "13.5 7.2 17.2": ["tamarin"], "4.3 10.2 19.7": ["noi"], "-2.5 9.4 0.3": ["rekeying"], "-3.6 2.6 13.2": ["desexing"], "-0.4 16.8 9.7": ["cachers"], "7.0 -4.1 4.6": ["portering"], "-1.2 0.3 2.9": ["microanalysis"], "6.6 9.2 9.3": ["modularly"], "0.6 1.3 -0.3": ["seaso"], "2.2 17.4 17.3": ["horseweed"], "1.4 7.1 8.0": ["haemorrhagic"], "11.9 9.2 17.8": ["tien"], "17.5 4.6 17.7": ["sailcloth"], "13.6 16.3 28.0": ["gamecock"], "9.4 5.7 4.3": ["pinksheets"], "-1.1 11.9 7.5": ["inculturation"], "2.9 7.8 4.4": ["adaptions"], "12.2 11.8 18.1": ["judy"], "10.8 2.1 -0.4": ["throughthe"], "9.3 14.9 16.8": ["overthought"], "13.3 1.9 4.2": ["thermographic", "immersible"], "4.1 -5.9 11.2": ["retiral"], "3.3 -2.2 10.4": ["cate"], "5.0 16.1 16.6": ["antihydrogen"], "8.1 12.5 23.4": ["celebreality"], "5.6 11.1 2.5": ["unamed"], "17.9 2.2 10.0": ["whiteware"], "1.7 -0.1 -0.3": ["seemlessly"], "16.0 5.3 10.3": ["tinkles"], "4.3 10.2 2.2": ["dilator"], "6.2 12.3 11.0": ["undelete"], "7.3 29.1 16.4": ["dragoon"], "3.0 6.3 10.1": ["nonmanufacturers"], "10.7 35.2 11.1": ["cylon"], "-0.5 2.4 18.3": ["deglaciation"], "12.1 13.2 13.1": ["showboated"], "15.1 20.5 7.2": ["unmourned"], "10.4 14.7 -0.4": ["warcrimes"], "25.4 8.5 41.8": ["piscine"], "0.7 3.0 4.9": ["notario"], "19.5 26.3 19.3": ["mozzies"], "-1.7 7.8 7.4": ["ejectment"], "19.7 5.0 23.2": ["squidgy"], "0.7 9.9 -1.5": ["ionizer"], "3.7 21.9 13.1": ["underhandedness"], "8.8 6.8 3.9": ["wheelarches"], "10.8 11.6 22.1": ["megathrust"], "-6.5 10.0 10.2": ["seroprotection"], "5.0 29.9 6.4": ["swiftboating"], "4.3 0.0 8.3": ["hanks"], "11.8 2.5 17.3": ["pinked"], "0.0 8.1 1.4": ["videoblog"], "10.3 4.7 21.5": ["chandlery"], "6.0 -6.4 6.3": ["yoh"], "4.2 9.5 1.4": ["scandalise"], "13.1 9.4 10.2": ["pneumatically"], "2.1 11.2 13.3": ["naringenin"], "0.4 7.3 9.1": ["daptomycin"], "10.3 10.2 9.5": ["transept"], "5.8 0.2 12.1": ["goji"], "-7.7 9.2 3.4": ["fft"], "3.7 10.5 6.4": ["bleatings"], "21.4 0.4 26.6": ["pastie"], "11.3 1.6 11.9": ["bioinformatic"], "-1.5 -3.6 0.2": ["unperformed"], "-4.4 4.3 6.6": ["consi"], "10.2 5.0 15.2": ["fieldtrip"], "10.4 2.0 6.2": ["takkies"], "4.3 11.2 18.0": ["basho", "timin"], "-2.0 1.8 -0.1": ["transcatheter"], "2.7 19.0 7.0": ["haji"], "9.9 13.3 10.6": ["theretofore"], "-3.8 -1.5 5.8": ["employement"], "9.2 2.9 8.1": ["shoehorns"], "-6.9 18.7 5.6": ["severer"], "9.9 12.8 27.9": ["knish"], "11.3 6.0 -5.5": ["novero"], "24.0 9.2 -2.3": ["acqusitions"], "5.6 3.7 -4.6": ["develoment"], "-4.6 1.2 -2.7": ["ates"], "1.6 11.5 -1.4": ["denominate"], "5.5 15.2 8.3": ["repressurize"], "4.8 12.2 4.2": ["exhumes"], "3.4 20.4 3.8": ["dishonours"], "23.5 2.9 11.0": ["spired"], "15.4 11.4 14.1": ["bawls"], "7.4 12.8 5.6": ["finis"], "-2.7 6.6 5.8": ["bibliographical"], "1.9 8.5 7.4": ["reppin"], "-5.3 4.0 23.0": ["liveweight"], "5.5 7.0 15.2": ["uncolored"], "5.0 13.0 6.1": ["twitterer"], "10.6 0.8 12.4": ["carryall"], "6.3 -0.3 17.0": ["gibson"], "-3.8 7.1 14.2": ["mahirap"], "14.3 7.7 11.0": ["xtube"], "11.1 4.5 15.1": ["tumblr"], "-0.5 9.5 11.2": ["pacquiao"], "8.1 12.1 14.4": ["jibberish"], "1.3 8.1 10.8": ["patchily"], "9.5 13.2 20.0": ["aragonite"], "7.8 5.2 7.4": ["nanosensor"], "11.9 10.3 8.9": ["distastefully"], "1.7 1.7 7.6": ["percen"], "3.9 13.0 7.3": ["hygroscopic"], "15.9 3.8 6.8": ["rehung"], "5.7 21.9 4.5": ["gutlessness"], "3.9 11.1 -1.0": ["sketchiest"], "13.6 13.5 12.3": ["scrollbar"], "9.4 10.4 12.0": ["handgrips"], "3.5 13.7 2.4": ["quaterfinals"], "7.4 18.6 14.0": ["armdrags"], "-8.6 -5.9 6.3": ["alotted"], "10.9 -0.9 7.2": ["prospection"], "-0.6 8.6 5.5": ["netlists"], "16.3 14.6 17.4": ["cruse"], "1.8 25.9 8.4": ["exclusionist"], "0.9 5.2 8.3": ["unemployement"], "-3.0 16.9 5.2": ["medievalist"], "7.1 5.2 12.4": ["phir"], "0.9 4.3 3.6": ["techincal"], "2.8 11.0 12.4": ["zygotes"], "20.7 1.4 29.8": ["chowing"], "2.9 10.4 11.9": ["cleanskin"], "-6.5 12.1 2.3": ["arousals"], "1.3 27.8 2.2": ["armourer"], "11.9 5.1 -2.6": ["productizing"], "-0.4 1.1 16.5": ["showlists"], "-2.9 5.7 41.6": ["scalloper"], "6.6 2.0 9.2": ["cinco"], "14.8 15.7 14.3": ["papparazzi"], "2.9 12.2 10.8": ["progenies"], "-3.7 12.4 14.6": ["asexuality"], "-2.9 9.6 4.0": ["peaker"], "3.8 14.0 7.6": ["allurements"], "5.4 19.5 10.7": ["sociopathy"], "9.7 -3.3 10.3": ["syndie"], "7.5 24.0 5.7": ["hacktivism"], "-2.5 5.1 13.4": ["shmita"], "4.2 21.1 4.8": ["abasement"], "3.0 5.6 6.3": ["helicase"], "6.1 -1.4 14.1": ["nis"], "8.7 5.6 29.1": ["tawa"], "-2.0 6.3 4.1": ["authoritativeness"], "21.8 4.8 2.6": ["benefaction"], "0.6 7.3 9.5": ["bildungsroman"], "4.3 15.1 7.9": ["ciliary"], "13.2 20.1 1.5": ["trustingly"], "1.8 3.0 10.9": ["bicyclers"], "-1.7 1.9 24.9": ["maunds"], "1.0 12.1 17.4": ["loquaciousness"], "6.8 1.6 0.4": ["underthe"], "6.4 -0.1 2.7": ["multidenominational"], "4.5 0.6 12.1": ["underfill"], "-3.9 0.9 12.2": ["namang"], "3.5 3.2 12.2": ["lak"], "4.3 5.8 9.1": ["plutons"], "10.2 3.9 15.0": ["magnifique"], "9.9 11.8 19.8": ["sepaktakraw"], "5.7 18.2 25.7": ["icepick"], "29.5 7.4 7.8": ["granddaddies"], "7.5 -0.1 9.4": ["lapdancing"], "1.0 17.5 12.8": ["kikamizu"], "9.8 6.6 37.1": ["hawksbill"], "1.9 4.2 2.5": ["overmedication"], "0.7 12.6 8.2": ["schoolmasters"], "8.4 9.4 19.5": ["baltimore"], "8.2 13.8 5.6": ["fone"], "9.3 11.9 5.2": ["villainize"], "-3.8 1.4 -0.3": ["uptimes"], "1.7 21.3 4.9": ["plainclothed"], "8.8 15.3 6.4": ["foresworn"], "7.0 12.7 10.3": ["mundanely"], "6.6 5.1 14.1": ["hame"], "3.2 6.0 2.3": ["racialised"], "8.5 -3.8 10.0": ["nen"], "5.8 19.2 0.6": ["abnegation"], "21.2 15.9 19.8": ["waterbug"], "11.2 0.5 20.1": ["cardi"], "5.5 6.4 5.3": ["kuwait"], "-6.6 9.3 6.9": ["sulfasalazine"], "-2.1 7.0 6.6": ["topcoats"], "11.2 0.3 17.6": ["bos"], "8.4 3.4 8.1": ["santos"], "2.7 10.0 14.8": ["perfused"], "-9.1 7.0 9.4": ["greyshirt"], "6.4 10.3 27.6": ["daphne"], "8.6 20.2 13.5": ["sledgers"], "3.0 11.3 11.6": ["bandas"], "-6.9 19.1 3.0": ["andthat"], "4.2 8.1 -7.8": ["vrs"], "3.5 -2.0 17.6": ["threeday"], "-6.7 16.5 8.5": ["sentimentalize"], "9.7 4.7 12.5": ["feminize"], "0.1 21.3 0.8": ["avowing"], "-3.2 9.8 9.5": ["sachin"], "12.9 11.4 19.8": ["wagonloads"], "6.2 0.8 7.1": ["pmc"], "5.3 17.6 8.2": ["inutile"], "17.0 5.2 14.7": ["flittering"], "9.6 -11.2 13.8": ["lun"], "3.0 6.0 8.5": ["disquisitions"], "-2.3 5.9 5.9": ["cookstoves"], "20.1 10.1 15.7": ["oaken"], "14.7 2.5 12.0": ["divans"], "17.5 24.4 14.2": ["charioteer"], "1.7 7.9 7.4": ["suc"], "0.4 13.3 9.8": ["becaus"], "12.8 14.0 7.5": ["edgily"], "-3.4 7.7 8.6": ["daunorubicin"], "6.3 5.2 15.6": ["holland"], "2.4 4.1 5.4": ["earcups"], "9.6 0.7 23.6": ["halfpenny"], "4.0 6.0 12.0": ["marcus"], "-2.1 5.6 2.4": ["birthmother"], "18.9 13.9 10.7": ["balefully"], "4.2 7.5 6.4": ["aller"], "5.5 1.9 6.7": ["valved"], "-4.7 5.6 7.5": ["noncarriers"], "7.7 6.5 17.0": ["deltaic"], "-3.7 -3.3 -0.0": ["audiological"], "-9.7 18.3 -0.6": ["hesder"], "11.0 3.9 9.6": ["larky"], "10.7 8.3 9.2": ["autosuggest"], "3.4 12.6 7.1": ["subdivides"], "11.9 15.9 10.4": ["animistic"], "19.0 2.3 11.2": ["milkaholic"], "8.5 6.4 10.3": ["erectus"], "9.3 -0.8 13.1": ["drinkware"], "0.5 15.4 26.8": ["charoset"], "5.7 11.8 9.1": ["behaviourally"], "-0.5 -0.0 1.7": ["copolyester"], "2.7 -0.5 3.9": ["acrylate"], "5.4 4.5 3.8": ["broomed"], "4.9 9.5 9.6": ["incremented"], "5.7 10.9 -3.3": ["reboarding"], "7.2 -0.6 2.9": ["retender"], "7.7 11.0 11.4": ["puppyish"], "9.4 -5.4 11.1": ["folklorico"], "-3.1 11.4 23.0": ["unfishable"], "9.5 9.6 10.8": ["empennage"], "15.6 9.2 17.7": ["tinis"], "9.8 9.5 10.8": ["skidmarks"], "5.1 7.1 4.3": ["agorot"], "-0.5 4.0 10.2": ["weathercast"], "10.6 -8.2 4.5": ["authentification"], "-6.9 19.0 3.5": ["fraternise"], "3.4 -0.3 11.7": ["lv"], "5.1 15.5 5.0": ["beacause"], "9.6 7.1 2.7": ["optimiser"], "8.5 13.6 4.3": ["flamboyancy"], "6.8 11.9 2.0": ["updaters"], "17.6 14.9 20.6": ["hoboes"], "17.6 4.6 25.3": ["colanders"], "0.3 9.8 2.8": ["outdriving"], "3.5 18.2 23.7": ["tansy"], "11.4 22.2 13.9": ["meeker"], "-1.1 16.8 6.3": ["interchangable"], "-0.2 17.3 2.6": ["fictionalizes"], "-5.8 17.4 10.0": ["haggadah"], "-9.4 3.2 3.9": ["atypia"], "7.0 4.7 -1.6": ["developped"], "16.7 10.4 2.0": ["roves"], "13.0 17.8 23.3": ["pyracantha"], "17.5 14.6 14.4": ["gasman"], "24.7 14.9 16.2": ["inscrutably"], "12.0 2.5 22.4": ["danishes"], "16.7 7.5 21.8": ["fluffiest"], "7.2 8.0 13.6": ["grainier"], "-0.4 28.5 2.9": ["religionist"], "-0.7 9.4 11.0": ["abhi"], "-3.6 5.3 13.3": ["eartips"], "-0.6 -6.8 2.8": ["avis"], "19.3 14.8 12.0": ["pfft"], "6.3 7.1 18.1": ["barkeeps"], "1.7 10.5 8.2": ["strokeful"], "5.4 8.0 33.1": ["satays"], "11.2 7.2 9.6": ["coagulates"], "1.5 5.9 10.8": ["adipocyte"], "-3.4 5.6 5.3": ["periodization"], "-4.9 4.7 5.7": ["cyclosporin"], "14.2 22.0 8.7": ["blam"], "-2.2 18.9 5.0": ["selectiveness"], "-7.0 8.8 7.1": ["ependymoma"], "4.4 11.7 -0.4": ["unconventionality"], "7.6 25.4 13.4": ["wogs"], "7.3 15.6 17.2": ["manlier"], "16.5 2.5 12.2": ["midways"], "2.7 3.0 13.6": ["showjumpers"], "17.8 10.2 5.3": ["jilt"], "11.4 12.1 13.1": ["clathrates"], "-0.8 28.9 14.0": ["sidequests"], "-3.9 17.9 2.7": ["historicals"], "-1.1 17.6 3.7": ["prejudicially"], "-0.3 13.2 21.3": ["lamping"], "11.6 8.4 18.3": ["trendies"], "4.3 7.1 40.5": ["zeppole"], "8.9 3.4 8.7": ["votre"], "4.8 3.0 11.6": ["cada"], "5.1 -7.0 6.1": ["cet"], "1.0 14.6 6.1": ["inconsiderately"], "3.3 10.4 11.8": ["romcoms"], "12.8 20.9 10.2": ["magnetron"], "7.2 11.5 20.7": ["tagalong"], "1.7 15.6 20.0": ["flatlander"], "-4.4 9.6 7.2": ["lytic"], "2.9 27.1 -0.2": ["akbar"], "7.8 16.9 4.5": ["georeferenced"], "15.2 10.8 18.1": ["tradtional"], "1.5 7.1 13.0": ["allophones"], "2.5 28.4 22.9": ["parasitoids"], "13.6 13.5 14.8": ["tards"], "0.8 8.6 3.7": ["saidhe"], "-3.7 6.7 16.6": ["astragalus"], "-0.5 16.0 7.4": ["unlived"], "8.2 21.7 3.8": ["honeytrap"], "5.2 14.0 6.5": ["muttawa"], "9.7 2.7 25.8": ["anthuriums"], "10.2 15.6 11.3": ["shesaid"], "19.7 21.9 15.5": ["slaughterer"], "22.6 3.1 1.5": ["speedbumps"], "10.5 14.2 10.0": ["paparrazi"], "6.0 7.1 12.9": ["aquatint"], "5.6 14.1 10.3": ["recalibrates"], "19.5 27.8 25.3": ["hellions"], "15.8 2.5 11.9": ["monty"], "-3.9 11.9 2.7": ["masjids"], "24.0 14.0 42.1": ["gastropods"], "11.5 14.0 11.7": ["officemate"], "1.9 9.8 7.6": ["moieties"], "1.4 5.4 17.0": ["unpreserved"], "-3.1 4.2 3.6": ["purpura"], "3.1 14.7 12.2": ["innerspring"], "6.8 4.5 11.6": ["slaking"], "-8.1 9.3 -2.2": ["qazi"], "-8.9 7.1 1.6": ["controvert"], "3.7 9.2 5.9": ["dethronement"], "7.5 7.6 18.1": ["sweepings"], "3.2 14.8 12.5": ["crossfader"], "6.8 -0.2 12.4": ["ringbacks"], "-4.1 16.8 4.5": ["repressors"], "2.2 38.9 6.3": ["monotheists"], "-1.4 3.3 0.7": ["softlines"], "5.8 15.2 16.5": ["wassailing"], "0.8 3.3 14.6": ["underthings"], "1.0 3.6 15.2": ["ction"], "-4.0 -0.0 7.3": ["spo"], "13.8 6.1 30.0": ["roes"], "2.0 18.2 3.9": ["passkey"], "16.1 9.9 11.7": ["rooves"], "2.9 14.2 8.9": ["ctrl"], "21.6 13.7 16.5": ["intertubes"], "1.2 7.4 6.2": ["stratigraphically"], "-13.3 7.6 3.6": ["nonoperative"], "4.9 15.6 6.9": ["sobriquets"], "4.8 13.3 6.0": ["compas"], "-1.5 0.8 10.3": ["mvp"], "18.9 6.9 14.3": ["fido"], "8.4 3.5 7.9": ["gie"], "-1.1 10.0 9.9": ["intraoperatively"], "12.7 -4.6 3.8": ["lifesciences"], "2.1 7.8 13.7": ["acetabulum"], "-3.6 8.6 15.3": ["gunsmithing"], "18.4 12.2 5.8": ["superconductive"], "6.4 -0.9 11.0": ["emersion"], "11.2 15.3 19.3": ["icemen"], "12.7 4.1 17.4": ["tailcoats"], "23.7 14.6 43.8": ["anglerfish"], "-1.5 -0.5 16.3": ["kundi"], "12.0 15.0 8.9": ["overleveraging"], "3.3 18.5 10.2": ["filmgoing"], "1.0 1.6 -3.3": ["artnet"], "10.5 2.5 30.0": ["otolith"], "3.3 5.2 11.1": ["kanye"], "11.0 0.9 35.0": ["dolmades"], "17.2 10.0 17.6": ["queasily"], "-2.9 4.5 8.6": ["pruritis"], "18.5 8.5 9.2": ["ebulliently"], "-7.9 4.8 13.8": ["varicocele"], "6.2 7.5 5.7": ["haveing"], "5.2 16.2 14.5": ["macroevolution", "cuerpo"], "3.5 1.0 5.4": ["configurators"], "4.2 9.2 3.1": ["retainment"], "-2.9 -6.9 4.1": ["ondemand"], "3.2 24.5 10.3": ["arcadey"], "5.9 0.8 4.1": ["wnt"], "-5.3 8.9 6.8": ["fulvestrant"], "3.2 6.7 2.7": ["veejay"], "6.3 2.9 20.2": ["plac"], "2.4 8.7 13.0": ["aaj"], "1.7 10.5 17.0": ["stratiform"], "13.9 7.5 -0.2": ["blackbox"], "10.4 -3.6 26.4": ["choi"], "-4.2 4.0 19.5": ["sewered"], "18.8 1.5 26.6": ["lamingtons"], "7.5 10.7 8.8": ["expendables"], "-2.4 6.4 9.7": ["nonproduction"], "-0.0 16.6 9.0": ["fanhood"], "10.4 3.8 10.4": ["icemakers"], "-6.5 10.4 5.3": ["transphobic"], "6.6 3.4 6.8": ["ene"], "0.2 -3.1 -0.0": ["nullnull"], "0.5 6.2 6.7": ["orthoses"], "-1.5 15.3 7.2": ["anthing"], "3.2 5.8 3.2": ["pressrelease"], "3.5 17.0 49.9": ["togue"], "7.4 11.8 4.2": ["innumerous"], "-4.2 -0.3 4.7": ["tocotrienol"], "-2.1 -1.4 15.3": ["ontrack"], "0.2 1.6 10.3": ["filmographies"], "6.5 15.3 14.6": ["missin"], "18.4 25.6 12.3": ["spacefaring"], "5.9 13.9 11.0": ["gentlewoman"], "-4.5 2.6 8.6": ["bility"], "7.9 9.2 16.7": ["dekho"], "16.7 5.3 21.3": ["pourer"], "6.0 11.7 8.5": ["vivaciousness"], "-4.9 3.5 1.6": ["participator"], "-12.4 4.1 -5.9": ["recepient"], "12.4 5.5 35.2": ["arancini"], "12.5 17.0 14.4": ["mouseover"], "11.8 -1.2 3.3": ["sextuplet"], "12.3 25.4 11.8": ["bringers"], "-3.6 16.4 12.3": ["falciparum"], "15.7 11.6 8.2": ["libidinal"], "9.6 3.9 29.5": ["chicharrones"], "8.9 10.7 13.5": ["christopher"], "-1.4 15.6 8.7": ["sherrif"], "1.5 -3.1 5.3": ["fice"], "2.3 2.0 15.8": ["marco"], "-0.3 6.6 7.2": ["protamine"], "23.0 6.5 7.9": ["toylike"], "21.9 10.0 24.4": ["jizz"], "6.8 2.1 7.5": ["sledded"], "-3.1 23.4 6.5": ["criminalities"], "17.1 3.6 9.6": ["ultraslim"], "4.3 16.5 14.9": ["bloodies"], "-0.4 19.9 5.5": ["monarchic"], "5.5 7.4 8.6": ["cowhands"], "9.8 12.6 15.0": ["unlooked"], "9.8 -7.4 0.4": ["docusoap"], "9.7 8.8 3.6": ["palliate"], "7.7 27.3 9.7": ["perfections"], "5.3 5.5 17.9": ["kiong"], "8.8 2.0 11.3": ["retablos"], "-8.4 -3.0 3.6": ["bekendmaking"], "2.8 21.1 8.0": ["insincerely"], "-0.8 11.2 7.3": ["arginase"], "9.7 11.3 23.8": ["kiters"], "-3.5 1.9 0.7": ["recomended"], "-2.6 15.6 -1.7": ["deras"], "17.0 15.9 10.2": ["reanimating"], "7.9 12.9 3.9": ["subversiveness"], "13.2 8.9 10.9": ["pithead"], "9.6 13.2 42.8": ["conger"], "0.3 14.1 1.5": ["dealbreakers"], "-2.3 6.5 -0.0": ["infructuous"], "7.2 10.9 1.0": ["sco"], "5.7 19.9 13.5": ["desaturated"], "4.2 2.0 11.6": ["geopark"], "9.4 9.4 38.1": ["forkfuls"], "2.4 2.2 14.7": ["tensioner"], "4.9 12.8 38.5": ["overharvest"], "6.5 22.8 8.4": ["libya"], "6.7 9.7 16.8": ["jang"], "7.6 3.2 9.2": ["recission"], "10.0 5.8 24.7": ["woollies"], "16.6 9.4 13.2": ["brandings"], "14.4 -0.8 5.2": ["syphoned"], "-3.0 3.3 -7.1": ["confernce"], "9.9 5.9 17.4": ["knurled"], "-3.3 -7.4 5.0": ["readvertise"], "10.2 10.6 13.9": ["giddyup"], "11.1 -2.7 -4.3": ["utl"], "15.2 -2.1 -5.3": ["pacted"], "-9.2 5.2 10.4": ["remyelination"], "7.0 14.6 13.1": ["greybeards"], "-2.9 8.7 0.6": ["nonsuit"], "7.2 9.4 9.1": ["foists"], "18.1 31.9 10.4": ["lightsabre"], "17.4 14.9 24.5": ["skidoo"], "16.5 9.2 17.9": ["teacakes"], "5.4 1.5 8.3": ["ritzier"], "9.6 9.9 11.6": ["kopeck"], "0.9 11.8 6.9": ["viewsheds"], "15.2 -4.7 12.1": ["telecaster"], "1.3 -1.9 20.7": ["jitneys"], "6.3 24.1 11.6": ["disturber"], "11.6 13.6 13.9": ["iveness"], "4.7 9.7 9.3": ["engraves"], "7.4 22.4 2.6": ["irreplacable"], "1.7 2.5 10.9": ["cardioid"], "3.0 15.0 34.0": ["bluewater"], "10.8 -0.4 -3.5": ["matchfixing"], "0.1 28.3 6.0": ["emplace"], "-1.3 2.4 16.2": ["hir"], "6.3 3.4 7.1": ["abr"], "26.6 9.4 15.1": ["jackalope"], "5.2 9.4 15.2": ["acidify"], "3.8 17.9 8.3": ["smallball"], "1.3 -7.4 2.9": ["investorrelations"], "-12.9 0.5 4.6": ["prevalences"], "19.7 12.2 10.1": ["trefoil"], "0.7 8.5 5.7": ["plano"], "2.4 8.1 3.1": ["elvitegravir"], "21.0 7.8 16.1": ["upturning"], "17.9 14.6 5.2": ["manufactory"], "-6.3 7.3 0.0": ["anaesthesiology"], "9.6 -0.6 14.1": ["seabuckthorn"], "1.2 1.3 20.7": ["tablescapes"], "0.1 2.5 -8.1": ["realeased"], "-11.0 9.2 2.1": ["extraditable"], "-0.7 5.0 0.7": ["inventorship"], "-4.3 9.2 7.9": ["foggier"], "4.7 18.3 14.0": ["airmass"], "6.8 -0.9 7.4": ["senicapoc"], "2.9 5.0 9.5": ["blks"], "11.2 7.5 11.3": ["surtaxes"], "2.0 4.1 20.2": ["tandoors"], "8.4 11.8 7.1": ["thugged"], "23.2 5.5 33.0": ["gateau"], "-6.6 3.3 6.1": ["dra"], "3.8 5.1 13.6": ["unzoned"], "-1.1 3.1 -6.7": ["debars"], "4.3 14.5 23.0": ["catmint"], "10.2 12.7 13.3": ["ranchos"], "16.7 3.9 3.5": ["xerox"], "14.7 13.9 17.8": ["killa"], "14.0 11.4 12.6": ["zat"], "13.9 15.8 3.9": ["hoster"], "2.0 10.9 7.6": ["suffusing"], "14.0 -2.7 21.8": ["breadmaking"], "6.2 9.7 9.4": ["hitchhikes"], "10.3 2.5 17.4": ["wenge"], "12.3 6.1 -6.8": ["merican"], "8.7 10.7 27.9": ["kaki"], "5.1 3.8 6.5": ["gluteal"], "6.0 5.9 1.6": ["rewriteable"], "16.3 6.8 18.7": ["strops"], "11.9 1.1 11.3": ["vises"], "0.5 8.7 26.0": ["sherbets"], "1.8 4.7 10.2": ["adrenoleukodystrophy"], "15.2 18.0 16.1": ["palindromes"], "7.8 7.8 9.5": ["bleh"], "15.4 19.2 5.2": ["quixotically"], "4.5 28.4 8.4": ["essense"], "12.0 -1.5 3.9": ["cheekier"], "-1.5 5.9 7.5": ["ils"], "12.3 6.8 17.7": ["sunseekers"], "1.8 9.7 12.3": ["sapphic"], "-0.1 9.0 8.8": ["bicalutamide"], "3.6 -1.1 6.8": ["vivre"], "4.9 -0.8 10.5": ["gucci"], "9.5 2.4 -3.2": ["heute"], "2.9 16.4 10.5": ["carders"], "8.3 8.0 31.0": ["potage"], "4.0 10.9 7.5": ["unpracticed"], "-0.6 10.5 11.1": ["hornfels"], "7.3 23.2 7.5": ["taxers"], "0.5 8.4 11.5": ["mesoderm"], "8.3 19.4 2.2": ["interrupter"], "-9.6 19.9 7.6": ["ullah"], "18.6 18.8 6.8": ["remould"], "-8.3 7.1 -4.4": ["objectiveness"], "1.5 -3.1 7.3": ["resum"], "5.9 7.6 10.2": ["evry"], "2.0 6.3 7.6": ["underutilisation"], "-1.2 12.4 4.9": ["politicked"], "-2.1 25.6 4.0": ["maimings"], "1.3 18.1 4.1": ["overemphasise"], "12.4 7.5 13.6": ["amethysts"], "17.2 12.6 10.3": ["multiculti"], "2.3 6.4 9.1": ["tcd"], "2.2 16.9 5.7": ["elide"], "10.8 11.6 9.0": ["occluding"], "3.9 10.7 14.1": ["sailboard"], "-0.9 -1.1 14.3": ["threemonth"], "8.0 14.6 3.2": ["nontheless"], "10.0 5.9 2.5": ["fmr"], "18.0 4.1 36.9": ["eggrolls"], "8.5 6.4 21.6": ["balmier"], "10.0 6.8 24.4": ["flagon"], "-12.9 12.3 11.1": ["polygyny"], "-7.5 13.3 3.5": ["biasness"], "4.3 16.4 11.3": ["deceptiveness"], "-1.2 4.4 -3.6": ["titleist"], "25.2 15.5 25.8": ["eggbeater"], "11.7 14.3 19.6": ["mouser"], "12.3 12.8 10.7": ["nosewheel"], "-2.5 -2.6 5.9": ["reconsiderations"], "9.8 5.2 7.0": ["strongroom"], "0.6 15.1 4.6": ["catholicity"], "2.2 3.1 -1.5": ["repsonse"], "10.9 11.1 10.5": ["milimeter"], "7.2 7.5 15.8": ["sultriness"], "7.2 12.8 21.7": ["rotifers"], "5.1 3.2 -4.5": ["thhe"], "1.4 14.0 17.5": ["blackleg"], "21.5 16.3 20.2": ["whirlybird"], "-0.8 31.1 1.6": ["kufr"], "6.4 1.3 10.5": ["esa"], "1.7 12.1 11.9": ["kababayan"], "-3.1 4.1 5.8": ["chs"], "-3.4 14.9 19.6": ["ergot"], "5.3 2.2 9.4": ["thurs"], "2.2 -2.8 16.9": ["wada"], "3.3 10.7 4.3": ["roomates"], "-2.3 11.1 11.0": ["statline"], "7.4 11.1 4.1": ["unaccommodating"], "4.1 12.0 -3.0": ["rousingly"], "2.9 5.8 14.1": ["twitosphere"], "15.2 21.3 15.4": ["grouches"], "9.7 20.8 9.1": ["vamoose"], "7.9 14.4 5.0": ["calamitously"], "4.8 7.0 30.3": ["freshwaters"], "11.5 8.0 30.5": ["swedes"], "-3.5 4.5 14.2": ["raindate"], "2.6 3.3 7.1": ["prohibitory"], "7.9 0.2 7.6": ["debe"], "21.5 6.1 -1.7": ["multistorey"], "17.7 25.8 6.9": ["lickspittle"], "5.4 22.7 -0.4": ["iranian"], "7.2 1.4 7.5": ["tantalite"], "-4.9 22.6 3.1": ["contry"], "18.1 15.1 8.2": ["hardmen"], "-1.2 1.1 21.1": ["tonsorial"], "14.2 35.2 19.8": ["shuriken"], "9.1 7.1 13.3": ["cigarillo"], "3.4 14.5 10.7": ["joyousness"], "-5.5 5.2 11.5": ["photojournalistic"], "4.0 14.7 9.2": ["mudras"], "0.2 11.6 7.6": ["mismanages"], "5.6 4.0 -1.2": ["alumn"], "6.8 0.4 2.3": ["perfumeries"], "4.2 6.2 7.8": ["irs"], "7.0 -3.9 4.6": ["anual"], "11.5 2.5 17.4": ["dancy"], "7.9 6.6 9.4": ["footplate"], "16.2 8.9 15.6": ["tranquilised"], "-1.7 1.2 10.3": ["equol"], "7.1 4.6 18.7": ["overbreeding"], "-1.2 -1.1 13.0": ["overcount"], "1.4 13.2 8.3": ["electromigration"], "6.5 0.6 3.6": ["zuh"], "-5.8 10.2 -3.2": ["congruency"], "16.0 1.0 31.4": ["tupperware"], "9.7 6.7 43.4": ["farfalle"], "10.8 16.6 10.8": ["enrapture"], "13.8 6.8 17.2": ["vulcanized"], "8.2 2.9 4.5": ["vanloads"], "8.5 7.6 32.2": ["pandan"], "15.9 7.0 5.6": ["liftout"], "-1.9 3.7 5.2": ["chukkers"], "12.9 4.1 14.4": ["semisolid"], "-0.7 -0.7 9.3": ["playday"], "-3.0 4.2 7.4": ["trafic"], "0.4 13.1 7.6": ["dubiousness"], "7.5 10.2 3.0": ["geed"], "8.3 8.1 30.6": ["starfruit"], "7.7 1.4 9.7": ["downpipes"], "24.6 7.8 29.6": ["humpbacked"], "5.5 -0.2 -7.4": ["affliated"], "11.5 0.1 11.4": ["hasa"], "17.6 12.9 26.5": ["upchuck"], "5.2 21.4 6.7": ["flatterers"], "3.5 11.5 8.5": ["depilatory"], "13.0 16.4 1.9": ["slapdown"], "5.2 4.2 14.8": ["janet"], "4.4 6.5 4.6": ["exper"], "2.8 4.3 13.6": ["upcharge"], "21.6 12.6 16.1": ["apelike"], "-0.8 6.1 5.8": ["superviser"], "13.5 8.0 33.1": ["gharial"], "-1.7 27.2 8.2": ["conscionable"], "4.0 17.1 7.9": ["fumigations"], "7.8 12.2 9.7": ["pedo"], "-2.4 14.4 15.0": ["overbuying"], "2.6 2.0 3.5": ["rol"], "1.8 -5.5 3.5": ["mahn"], "-1.9 -4.6 0.1": ["collateralisation"], "11.4 17.2 16.2": ["overgrow"], "4.7 9.0 14.2": ["neonicotinoids"], "-2.0 -9.5 5.7": ["norandrosterone"], "4.5 11.3 12.3": ["towelled"], "8.2 10.1 22.4": ["floribunda"], "-4.4 -0.5 -5.4": ["lof"], "12.2 8.4 5.5": ["wracks"], "3.0 15.2 12.6": ["jbox"], "9.8 6.3 12.5": ["undercoating"], "6.5 5.8 32.7": ["lasagnas"], "0.5 -2.4 6.2": ["musicans"], "21.4 15.2 13.5": ["shininess"], "-4.4 11.6 7.6": ["nonmalignant"], "9.2 25.2 8.1": ["insidiousness"], "14.2 9.1 15.6": ["mummify"], "10.2 10.7 18.3": ["strakes"], "5.8 8.0 22.1": ["oilier"], "13.6 14.4 5.5": ["gabber"], "7.8 4.0 -0.0": ["leasebacks"], "3.1 13.4 7.5": ["spasmed"], "20.8 6.6 8.0": ["goldminer"], "-1.3 25.4 9.3": ["antipathies"], "6.1 20.8 1.2": ["mythologised"], "-0.5 8.4 4.5": ["reselection"], "-8.5 6.6 3.2": ["contractures"], "2.0 10.2 14.1": ["bure"], "22.0 0.7 12.6": ["millio"], "9.5 12.2 3.7": ["hyderabad"], "3.4 10.7 8.0": ["pyridine"], "19.0 17.9 15.1": ["diety"], "1.5 6.6 13.4": ["triclocarban"], "17.6 10.2 6.8": ["ita"], "2.3 5.7 1.3": ["backsheets"], "7.5 19.2 6.5": ["theodicy"], "8.4 4.9 15.8": ["ferromanganese"], "9.3 11.3 5.2": ["simul"], "11.9 15.7 22.4": ["wirework"], "-0.9 15.1 10.0": ["charisms"], "-3.0 15.9 13.1": ["tightheads"], "12.0 6.2 7.6": ["overstimulating"], "3.0 28.5 7.5": ["idealogy"], "-2.6 4.5 9.0": ["oestradiol"], "-2.0 5.7 19.3": ["coning"], "5.9 3.5 3.3": ["anatomists"], "20.6 6.1 13.1": ["purdy"], "5.0 27.8 12.4": ["splitscreen"], "0.2 18.4 1.2": ["allthe"], "10.5 10.6 3.8": ["tonked"], "3.3 -9.5 -9.9": ["inclduing"], "6.9 8.0 14.1": ["andre"], "-3.0 -1.8 1.3": ["weekened"], "13.0 8.6 10.5": ["texturizing"], "8.2 22.0 6.9": ["chevalier"], "16.7 6.8 21.1": ["petaled"], "0.6 10.9 3.2": ["effeciently"], "-3.0 10.8 3.2": ["gondeee"], "3.4 6.3 18.6": ["derek"], "16.2 1.0 13.1": ["etail"], "3.3 12.4 26.5": ["kibbeh"], "1.9 6.4 24.4": ["pisciculture"], "-5.3 0.3 -0.1": ["physican"], "3.4 1.6 2.3": ["cycler"], "10.1 11.8 12.7": ["rasa"], "18.4 5.2 15.4": ["yellowy"], "7.2 14.5 8.4": ["freeriders"], "15.5 12.8 12.6": ["arbs"], "2.0 11.9 -3.8": ["indymedia"], "11.3 4.6 9.9": ["wooo"], "21.2 16.7 22.8": ["homunculus"], "11.9 18.9 17.9": ["muckers"], "19.1 7.5 16.9": ["andirons"], "-7.3 6.8 5.4": ["macrocells"], "6.1 10.0 11.2": ["babas"], "2.9 21.5 13.1": ["remorsefully"], "9.0 36.1 8.8": ["hireling"], "9.8 1.7 13.4": ["plimsolls"], "3.8 10.2 23.0": ["kababs"], "-2.6 0.3 10.7": ["musicological"], "3.8 8.7 9.6": ["etude"], "17.5 14.6 20.1": ["hiney"], "7.6 5.5 7.6": ["weakend"], "1.2 1.6 8.4": ["mahapanchayat"], "16.5 9.3 7.2": ["trainwrecks"], "7.6 11.8 12.9": ["airheaded"], "12.1 9.6 9.7": ["gora"], "5.5 10.4 7.4": ["hydroformed"], "8.2 -6.3 12.3": ["unfroze"], "-1.3 7.9 8.6": ["shipsets"], "19.5 12.7 17.7": ["acer"], "3.7 -4.1 18.2": ["lian"], "12.6 0.4 14.9": ["shrinkwrap"], "7.5 14.6 5.7": ["ghettoize"], "3.0 12.0 13.0": ["radiometrics"], "1.9 9.4 -0.3": ["jubilations"], "12.2 1.3 24.9": ["tupelo"], "12.5 8.2 19.7": ["gyp"], "10.1 21.9 2.1": ["fatuously"], "-0.3 1.3 2.6": ["lumiracoxib"], "5.3 1.5 0.0": ["ipsh"], "9.3 4.7 5.5": ["maser"], "8.5 10.0 7.0": ["cavalcades"], "-12.7 16.6 -1.1": ["questionings"], "6.7 12.7 7.8": ["combusts"], "19.4 7.7 23.2": ["iest"], "-0.5 3.7 7.7": ["nonscripted"], "13.3 6.5 9.8": ["upswell"], "15.3 15.5 11.9": ["slimiest"], "4.6 10.8 1.6": ["glamourised"], "-0.9 4.1 1.8": ["pentane"], "-1.3 11.7 9.7": ["moksha"], "4.4 1.9 11.1": ["ambrose"], "-9.4 10.3 1.6": ["bronchodilation"], "-3.4 7.6 10.7": ["huntingtin"], "-3.4 -0.5 3.0": ["toric"], "5.4 5.0 11.7": ["whereat"], "10.3 12.8 8.5": ["airfoils"], "-3.5 6.9 3.9": ["deduplicate"], "-0.3 8.9 0.2": ["sermonized"], "10.9 11.5 7.2": ["pressurizes"], "-8.2 24.1 5.5": ["precautious"], "11.5 -3.2 -2.9": ["blagged"], "-2.1 22.7 10.2": ["confessionalism"], "3.1 10.5 10.8": ["arboretums"], "8.4 21.1 15.1": ["xylem"], "7.8 3.3 -3.9": ["wiil"], "-3.8 5.6 -1.4": ["contestations"], "-0.7 4.8 7.9": ["caucasians"], "-1.2 15.3 5.0": ["localist"], "3.0 6.2 11.3": ["lungful"], "7.4 3.7 3.0": ["thecity"], "0.5 10.2 7.1": ["repass"], "14.3 8.6 12.3": ["zeta"], "-0.1 6.7 7.0": ["equitability"], "1.7 10.1 5.8": ["subcritical"], "3.6 16.5 7.0": ["equipage"], "2.5 9.8 5.3": ["sneakerheads"], "14.9 11.1 9.8": ["crossdressing"], "4.4 5.4 2.5": ["valorisation"], "20.2 5.9 12.8": ["rackety"], "5.3 14.1 2.3": ["nomenclatures"], "10.1 10.4 11.0": ["diviners"], "-4.8 19.7 8.5": ["ruleset"], "9.0 8.1 -4.5": ["correctors"], "3.7 10.6 9.4": ["derecho"], "3.0 9.0 9.9": ["writin"], "-1.5 4.3 6.4": ["disulfiram"], "-9.2 8.9 -0.2": ["assumable"], "-2.6 11.3 18.4": ["metastable"], "2.1 -0.2 9.4": ["epichlorohydrin"], "6.9 6.8 19.2": ["aquanauts"], "-2.8 4.5 7.2": ["hassidic"], "7.4 7.2 -0.4": ["alow"], "3.2 22.2 14.4": ["sidespin"], "-7.1 8.4 5.9": ["priviledges"], "20.1 2.8 10.3": ["spankin"], "-1.3 0.2 5.4": ["nonobese"], "8.7 16.2 13.8": ["handmaid"], "8.8 18.6 -3.1": ["controversialist"], "4.8 4.6 14.6": ["braais"], "5.4 8.6 6.3": ["dirucotide"], "5.2 14.0 27.1": ["oxbows"], "2.2 6.8 9.6": ["durin"], "8.9 9.0 6.2": ["priceline"], "16.7 16.1 14.6": ["crackberry"], "4.1 6.9 11.7": ["ladettes"], "7.8 14.1 4.7": ["itwill"], "8.5 11.4 13.3": ["sleeving"], "-2.3 5.0 6.4": ["venipuncture", "newz"], "14.4 10.4 9.4": ["monkeyed"], "9.7 4.6 37.3": ["tostones"], "-1.7 11.8 -0.5": ["happenned"], "-1.3 -8.1 2.2": ["sions"], "6.6 4.8 10.6": ["altarpieces"], "2.1 28.4 -1.1": ["hamas"], "4.4 15.5 19.8": ["symbiont"], "-6.8 3.8 4.0": ["linecard"], "5.9 13.4 6.6": ["boundlessly"], "13.2 0.6 12.5": ["supercasinos"], "1.0 11.0 -0.6": ["paramountcy"], "14.8 6.9 2.3": ["recoveri"], "14.9 14.0 5.9": ["precursory"], "17.9 -0.3 17.9": ["gobo"], "-0.9 10.1 -3.3": ["tasimelteon"], "-7.8 3.6 18.3": ["reeves"], "1.8 8.9 13.0": ["interring"], "5.2 28.1 3.9": ["holstering"], "-0.1 4.5 15.7": ["unseasonally"], "14.0 4.0 12.6": ["imac"], "8.8 20.7 10.7": ["recolonization"], "8.7 -0.6 -3.6": ["livestreaming"], "-6.1 19.8 16.1": ["overcards"], "7.7 4.9 13.2": ["utsav"], "11.4 9.8 6.4": ["fundie"], "2.2 9.6 4.5": ["monomeric"], "-16.5 16.8 -1.8": ["inculpatory"], "8.3 11.6 10.6": ["sackless"], "2.6 8.6 5.2": ["ible"], "0.6 3.0 3.2": ["opportunies"], "3.2 10.6 7.2": ["sodomise"], "0.9 20.9 12.4": ["synovium"], "-5.8 -2.8 9.8": ["nonathletes"], "10.8 7.7 17.5": ["terre"], "10.0 -3.2 -3.5": ["accomodates"], "7.8 6.0 14.2": ["ladyboy"], "0.5 13.6 19.3": ["disking"], "-7.5 10.5 0.9": ["stoichiometric"], "-5.0 3.9 10.6": ["elasticities"], "9.4 4.3 7.0": ["stoushes"], "4.8 18.9 6.4": ["devaluating"], "-3.4 10.8 15.0": ["lambic"], "4.2 7.9 5.5": ["homeliness"], "4.1 4.9 3.9": ["tasocitinib"], "10.1 41.9 9.6": ["mercs"], "13.2 4.4 16.7": ["bois"], "8.3 20.8 4.9": ["orientalism"], "6.6 12.0 21.3": ["belladonna"], "-2.7 3.8 12.8": ["ila"], "7.6 19.9 5.9": ["bewitches"], "4.7 4.9 0.8": ["redistributors"], "3.7 -8.6 0.0": ["telecommutes"], "15.5 9.3 23.8": ["boatshed"], "11.2 16.3 15.3": ["unnavigable"], "-3.3 4.7 13.5": ["karyotype"], "4.7 15.9 -0.6": ["nameservers"], "8.5 13.6 0.0": ["ensconce"], "-4.5 9.5 7.9": ["documentable"], "6.0 26.2 3.8": ["desists"], "-0.4 -1.9 10.9": ["garde"], "1.7 13.0 4.6": ["economizers"], "2.8 6.7 2.2": ["hypothecated"], "-1.3 3.8 -2.6": ["supersession"], "3.0 -1.1 13.5": ["receival"], "8.5 9.9 16.3": ["roughen"], "5.0 -5.5 13.1": ["stude"], "5.6 6.1 25.2": ["sammy"], "6.9 3.3 4.7": ["finsh"], "3.6 10.6 -3.1": ["aerodynamicists"], "5.2 18.8 -7.3": ["taks"], "-1.4 6.3 10.1": ["jhuggis"], "-3.4 1.5 2.7": ["cetane"], "7.2 15.4 9.2": ["encasements"], "10.8 5.7 -5.0": ["gedas"], "-5.8 31.1 7.7": ["mortarman"], "15.5 8.3 14.8": ["uncapping"], "7.9 6.4 14.0": ["gaokao"], "-8.3 4.8 1.1": ["subtests"], "2.4 -5.7 -1.1": ["isavailable"], "-2.5 4.2 7.2": ["laya"], "-7.7 6.9 7.5": ["photodamage"], "7.2 7.4 10.2": ["remanufacturers"], "11.2 22.6 2.0": ["indefatigability"], "7.5 0.2 16.4": ["sheepherding"], "5.1 1.7 15.8": ["tonsure"], "1.5 0.6 -0.4": ["earthmine"], "10.2 9.9 8.3": ["compendiums"], "-7.8 17.1 6.7": ["correctible"], "5.2 13.0 5.5": ["geosynchronous"], "-2.5 20.2 4.5": ["mukhtar"], "6.6 14.1 3.8": ["overvalues"], "-2.8 15.6 11.6": ["flashforward"], "13.1 -0.5 5.8": ["hyd"], "7.6 19.2 11.7": ["drat"], "5.8 9.1 17.9": ["bussers"], "14.1 10.5 6.6": ["removeable"], "11.5 7.2 7.6": ["unimpressively"], "5.3 15.6 3.6": ["hairsbreadth"], "12.8 16.3 11.1": ["hahah"], "0.7 12.2 7.6": ["ploddingly"], "7.6 11.6 13.4": ["jauntiness"], "-0.1 4.0 11.5": ["cytosolic"], "-0.3 14.0 6.6": ["kabbalistic"], "7.6 4.7 19.7": ["kristen"], "7.8 11.0 3.5": ["thenation"], "-12.2 8.1 -0.6": ["stenoses"], "-5.9 7.3 3.6": ["sulphonylurea"], "-0.0 19.4 11.6": ["shotmakers"], "-3.6 20.0 15.7": ["streakiness"], "10.8 0.8 12.2": ["mississippi"], "-6.0 11.2 9.6": ["carcinoid"], "19.4 17.8 23.2": ["galoot"], "-0.2 4.3 4.7": ["implemention"], "4.7 -0.3 13.3": ["kisspeptin"], "-0.1 13.3 12.4": ["airspeeds"], "15.2 -6.3 9.8": ["ehn"], "-1.1 3.9 11.4": ["kameez"], "3.8 11.6 32.4": ["mosquitofish"], "1.2 19.1 3.9": ["themselve"], "11.0 5.6 9.1": ["brassware"], "-4.3 3.1 4.2": ["mbar"], "-0.1 6.8 4.9": ["uninstallation"], "-0.2 6.4 5.6": ["gaurantee"], "0.9 10.1 1.8": ["dissappointing"], "-10.0 3.7 6.3": ["externed"], "17.1 1.0 11.9": ["tipis"], "3.2 10.6 17.5": ["jes"], "-0.5 10.7 12.4": ["sinha"], "-1.1 10.6 5.6": ["colorguard"], "7.0 6.0 8.6": ["powderpuff"], "6.4 5.6 17.7": ["shou"], "5.9 4.5 13.8": ["natalie"], "3.1 13.0 2.8": ["weare"], "-0.9 17.1 9.3": ["backslides"], "-6.9 3.5 2.3": ["telepsychiatry"], "18.1 2.4 15.4": ["flummery"], "11.9 5.3 13.8": ["booboo"], "-0.8 14.9 0.7": ["thetwo"], "6.7 36.0 12.6": ["darkspawn"], "-0.5 3.5 3.1": ["unpartnered"], "8.7 5.4 39.7": ["reuben"], "20.9 1.2 5.0": ["ultracheap"], "14.3 4.9 7.5": ["homebrewed"], "8.3 12.6 12.9": ["batterings"], "14.7 -2.0 13.7": ["wheely"], "6.2 11.1 8.7": ["mocap"], "12.3 9.6 10.5": ["mischevious"], "1.7 12.0 5.4": ["perversities"], "-6.8 17.6 1.7": ["exemplification"], "7.6 6.0 8.9": ["untuk"], "3.2 7.4 20.4": ["dili"], "5.1 4.1 12.5": ["simpson"], "24.6 14.6 19.4": ["bigmouth"], "9.9 11.6 19.1": ["apiarists"], "7.3 13.9 15.4": ["handclap"], "-0.2 8.1 7.5": ["timbral"], "2.5 18.7 6.3": ["forseeable"], "8.6 11.3 18.4": ["jacob"], "12.9 9.4 31.8": ["tussocks"], "15.1 7.5 46.2": ["spoonbill"], "-10.3 3.9 -4.8": ["thrombolytics"], "-4.0 16.3 -0.4": ["chareidi"], "6.9 14.4 12.9": ["virion"], "26.0 10.4 14.3": ["spastically"], "-0.4 -2.5 8.2": ["anually"], "4.4 -5.3 7.8": ["mmtpa"], "15.3 9.9 38.3": ["toadfish"], "4.9 4.3 7.7": ["wek"], "4.5 2.2 3.9": ["concepting"], "10.5 3.2 10.1": ["lowed"], "-0.8 13.5 3.4": ["sermonize"], "0.9 1.8 10.6": ["ketubah"], "8.5 9.6 10.5": ["inners"], "5.5 15.3 13.2": ["profundities"], "9.2 13.5 1.2": ["stright"], "4.0 15.3 29.2": ["gimlet"], "0.2 1.3 4.4": ["practicioners"], "3.0 19.0 15.8": ["overvote"], "24.1 3.6 14.5": ["lollapalooza"], "-5.3 7.0 9.4": ["mangaka"], "-3.2 1.3 -4.0": ["inteview"], "12.9 10.4 17.8": ["manana"], "5.7 16.8 13.5": ["catastrophy"], "6.3 6.0 12.8": ["woodburning"], "14.5 32.6 4.1": ["disorientate"], "6.9 20.3 14.6": ["sabra"], "-4.5 3.9 9.8": ["inspectional"], "-6.0 6.0 9.5": ["fifteens"], "2.5 5.6 6.5": ["powercuts"], "-6.1 5.2 3.5": ["recanalization"], "10.3 14.6 -0.2": ["borked"], "0.1 13.7 7.5": ["overshare"], "11.2 2.0 10.9": ["unsnarl"], "3.8 12.5 17.7": ["pallu"], "2.7 6.6 11.1": ["alphabetize"], "9.7 7.7 1.9": ["gor"], "8.8 7.9 5.3": ["yukked"], "20.0 7.0 10.9": ["twiddles"], "12.0 0.8 9.3": ["priv"], "4.3 -1.7 21.5": ["stella"], "11.9 12.1 2.0": ["seemless"], "1.5 16.4 9.3": ["pseudomonas"], "3.8 12.0 17.7": ["headwaiter"], "-0.9 10.1 5.6": ["packetized"], "-4.7 8.5 6.0": ["doorstaff"], "16.1 25.2 18.5": ["palisades"], "-8.6 7.0 6.3": ["myelodysplasia"], "-1.8 7.7 6.5": ["marlas"], "12.5 16.5 12.0": ["submicroscopic"], "-1.4 9.7 10.4": ["platonically"], "10.4 9.6 11.1": ["kaboodle"], "2.7 6.8 23.5": ["downlisting"], "-1.9 8.8 6.0": ["sinbinning"], "22.9 -6.1 -1.6": ["flexibles"], "10.7 9.7 13.5": ["clotheslining"], "3.6 14.0 5.6": ["recraft"], "7.7 20.3 2.5": ["sneezer"], "-1.2 12.5 12.6": ["mokopuna"], "5.8 17.4 9.3": ["presidio"], "7.6 30.3 7.9": ["oldness"], "20.9 13.5 11.7": ["ubiquitousness"], "8.0 4.0 16.0": ["nontradable"], "4.9 1.4 15.1": ["mobos"], "6.9 1.9 4.2": ["zwei"], "-3.2 5.0 3.7": ["cessions"], "7.7 4.0 15.4": ["scratchboard"], "2.3 14.4 20.1": ["medulla"], "4.3 4.7 -0.5": ["millenials"], "13.6 19.2 1.2": ["overnment"], "0.0 8.6 20.2": ["bifidobacteria"], "8.1 4.3 38.7": ["clambakes"], "2.5 2.7 5.4": ["passporting"], "17.6 8.7 7.9": ["supercentre"], "14.4 22.3 16.8": ["spoor"], "6.3 7.6 14.5": ["cavs"], "6.3 0.3 8.3": ["paseo"], "4.1 9.3 15.2": ["kabhi"], "12.7 29.0 17.0": ["swines"], "10.3 16.0 33.3": ["fatheads"], "1.3 0.0 14.8": ["undertray"], "5.5 -3.6 7.6": ["gyda"], "8.2 4.0 15.1": ["mellotron"], "0.9 -4.2 5.8": ["erythritol"], "-4.8 14.2 4.7": ["sideouts"], "12.3 2.4 11.7": ["longjohns"], "23.1 6.5 22.7": ["runty"], "-0.1 -1.4 3.1": ["reaccelerating"], "-9.5 9.7 6.2": ["disfavors"], "7.1 9.1 10.2": ["desking"], "-3.9 6.0 9.7": ["trach"], "15.4 14.9 12.4": ["conjuror"], "6.5 10.0 13.3": ["learnin"], "10.2 29.6 6.8": ["subhumans"], "11.0 23.1 43.8": ["spartina"], "-2.1 7.8 8.8": ["stablehand"], "-4.5 14.1 -2.1": ["underresourced"], "-3.0 1.2 11.2": ["liv"], "12.0 -3.3 9.9": ["rehang"], "-3.6 3.0 9.7": ["sharma"], "6.4 1.5 12.1": ["delineators"], "0.9 12.4 4.6": ["unsportsman"], "5.8 19.7 -0.1": ["totalizing"], "7.8 4.2 13.6": ["metagenomic"], "4.0 24.6 10.0": ["asker"], "6.6 6.7 8.4": ["sunblocks"], "-8.1 -0.4 1.4": ["methylprednisolone"], "2.4 15.9 14.4": ["sensualist"], "14.3 10.4 22.8": ["liger"], "-2.4 3.8 5.5": ["anionic"], "-7.2 10.2 6.6": ["thymic"], "13.1 24.2 19.6": ["quicksands"], "-2.2 15.7 2.9": ["dawa"], "13.3 13.0 18.2": ["hornbeam"], "-5.3 9.3 12.5": ["preauthorized"], "9.8 -0.0 32.1": ["soggier"], "23.8 11.1 7.2": ["jerkily"], "18.5 -1.1 1.9": ["informercials"], "10.2 22.6 17.5": ["espalier"], "7.5 15.6 15.4": ["pif"], "6.4 12.5 6.2": ["msm", "rectifiable"], "4.3 -0.9 18.8": ["ethnobotany"], "-9.7 25.0 7.2": ["disheartens"], "11.3 18.3 4.8": ["audaciousness"], "1.8 9.6 7.9": ["keyer"], "10.6 13.0 8.3": ["prosperously"], "12.0 7.4 2.2": ["thefuture"], "5.0 9.3 13.2": ["ducat"], "-4.5 -1.3 -1.4": ["neuropsychologists"], "4.5 12.4 10.0": ["pelters"], "4.3 -0.4 2.1": ["clos"], "10.3 0.9 -3.5": ["platformed"], "6.6 11.0 9.2": ["underhit"], "1.2 23.2 11.7": ["counterplay"], "-1.6 13.3 7.8": ["splenic"], "6.5 13.5 10.4": ["handiness"], "1.8 31.4 10.4": ["fellowman"], "3.9 3.1 1.4": ["florbetapir"], "2.3 7.8 10.5": ["babyfaced"], "9.9 7.6 32.5": ["ulu"], "5.9 -5.8 5.1": ["sz"], "-2.0 -2.9 7.5": ["decatherm"], "4.5 12.0 3.3": ["probally"], "7.0 -9.7 4.2": ["particpating"], "8.6 -0.5 14.4": ["sparklingly"], "20.0 12.4 13.4": ["vacs"], "-0.8 18.4 14.1": ["unpremeditated"], "2.5 5.7 9.2": ["lowish"], "3.2 3.7 13.4": ["drainfield"], "13.3 20.6 4.5": ["adamantine"], "11.8 9.3 13.1": ["chuch"], "6.9 8.9 9.6": ["limbus"], "20.2 5.4 6.7": ["goldmining"], "7.3 -0.8 17.8": ["tiffins"], "-4.7 1.0 3.0": ["pitavastatin"], "10.4 20.4 7.5": ["sounders"], "9.4 19.8 0.1": ["challege"], "1.5 7.4 18.4": ["fescues"], "6.9 9.9 6.7": ["goalled"], "-1.2 6.3 11.0": ["petrols"], "2.3 10.3 5.0": ["thumbdrive"], "1.3 4.2 13.1": ["pageboys"], "4.9 9.1 12.3": ["nathan"], "-4.3 7.1 7.7": ["overdrafted"], "8.8 -6.2 13.9": ["svc"], "7.5 0.4 15.3": ["calcutta"], "5.7 8.8 3.6": ["nettled"], "23.0 12.2 8.7": ["toyland"], "6.9 10.4 12.0": ["superlens"], "17.9 1.7 18.0": ["dol"], "1.1 19.2 2.8": ["autofocusing"], "15.7 4.8 16.7": ["coopers"], "0.0 -1.5 13.0": ["maltsters"], "-3.3 9.1 2.0": ["pulseless"], "8.0 9.4 4.2": ["teched"], "2.0 9.9 15.4": ["brightener"], "6.0 2.1 24.1": ["pounamu"], "-8.1 23.5 14.2": ["middlegame"], "11.9 2.3 8.8": ["agglomerated"], "11.3 12.8 10.9": ["overbearingly"], "3.7 4.4 9.9": ["lowlighted"], "-1.3 10.6 14.3": ["shalwar"], "-2.4 16.6 3.8": ["homelife"], "1.7 16.2 9.8": ["tarai"], "11.0 5.5 22.3": ["elegans"], "1.5 9.4 13.1": ["melodramatics"], "3.6 20.8 9.7": ["riboswitch"], "15.3 11.8 13.9": ["overblowing", "tarmacadam"], "-1.8 2.0 9.1": ["unblended"], "17.0 13.8 4.0": ["contritely"], "8.4 24.6 6.5": ["soverign"], "10.3 6.9 12.6": ["hallyu"], "10.4 10.6 47.9": ["sprat"], "5.1 1.6 0.4": ["exhibiton"], "6.5 -6.7 4.6": ["ering"], "-2.2 15.8 5.4": ["gyroplane"], "5.6 4.6 -2.3": ["telephonist"], "14.1 10.7 7.2": ["escapologist"], "1.0 2.4 -6.0": ["comissioner"], "-2.7 -1.2 -0.6": ["neuropathological"], "8.2 -3.4 2.7": ["csr"], "-5.7 10.1 18.6": ["doda"], "-0.8 4.3 14.8": ["mmj"], "2.6 6.0 0.8": ["banns"], "-3.1 2.8 4.5": ["runscorer"], "0.4 19.5 22.0": ["alts"], "14.6 3.4 19.7": ["dendrochronology"], "13.8 13.8 20.2": ["litterbox"], "3.4 8.6 25.5": ["roasty"], "7.3 1.9 4.7": ["truckstops"], "18.4 7.3 21.7": ["monte"], "-0.5 6.4 5.7": ["aspheric"], "8.3 12.4 9.4": ["indentity"], "-2.3 8.7 1.6": ["lifeflighted"], "1.4 -4.4 20.4": ["sev"], "11.9 4.0 9.5": ["studbooks"], "4.0 -5.3 11.3": ["nez"], "4.1 16.9 5.5": ["furthur"], "13.1 19.3 13.5": ["occultists"], "-8.2 13.9 9.5": ["intermarrying"], "15.3 6.4 17.1": ["bobtail"], "25.7 14.6 8.7": ["tightropes"], "10.7 7.4 16.1": ["elastically"], "3.5 15.9 10.0": ["atrophies"], "5.8 10.6 12.0": ["thanda"], "13.1 9.0 6.4": ["douching"], "5.2 5.4 9.5": ["overemphasizes"], "-1.5 13.2 9.8": ["phosphatidylserine"], "8.6 2.6 12.4": ["aprox"], "0.6 22.4 5.3": ["peoplehood"], "12.0 7.1 8.0": ["costliness"], "14.3 4.1 4.8": ["multicolour"], "9.4 6.2 12.4": ["stumpers"], "12.5 10.0 37.5": ["kittiwakes"], "8.8 1.9 19.9": ["reo"], "0.8 3.1 2.5": ["alagebrium"], "-5.6 -5.6 -0.9": ["minues"], "23.1 -5.1 0.3": ["marketweight"], "4.1 13.2 5.9": ["photocatalyst"], "-0.8 3.4 6.2": ["mezuzahs"], "2.8 26.0 -2.7": ["casuality"], "16.5 5.3 14.4": ["mounties"], "16.6 24.0 20.6": ["blighter"], "6.7 19.5 7.9": ["thuggishness"], "1.0 2.6 14.1": ["bryan"], "10.7 9.1 15.8": ["darning"], "-2.7 6.3 -0.2": ["sangh"], "2.2 11.8 1.1": ["untestable"], "1.9 5.5 9.5": ["cyclin"], "1.9 8.8 7.4": ["langdonj"], "-0.7 17.1 6.2": ["conceeding"], "11.0 28.1 9.4": ["vengefully"], "0.5 -7.3 0.9": ["cosponsorship"], "8.0 11.5 13.1": ["mudstones"], "8.0 20.0 4.8": ["populaces"], "9.1 0.5 10.3": ["seung"], "-0.3 8.8 2.3": ["quarterof"], "9.6 5.8 31.9": ["gingersnaps"], "7.2 0.3 -13.2": ["juwi"], "13.1 1.1 -9.3": ["devlopment"], "14.1 5.1 11.9": ["buckaroo"], "6.8 9.8 26.6": ["tenderizes"], "0.8 2.4 0.6": ["extracorporeal"], "17.4 12.7 12.2": ["esqe"], "4.1 4.0 -2.0": ["betandwin"], "10.6 24.9 9.2": ["spiting"], "-4.1 -0.5 -7.6": ["adressing"], "-5.6 3.6 3.3": ["rhinosinusitis"], "-6.9 3.9 -0.2": ["neccesarily"], "10.1 17.9 30.8": ["euonymus"], "-0.3 3.0 13.3": ["unc"], "-4.0 8.5 10.2": ["destress"], "1.0 4.9 14.3": ["nyo"], "6.8 18.5 8.1": ["horridly"], "2.7 9.1 11.7": ["minicabs"], "3.4 13.9 -4.0": ["expertises"], "-4.2 14.7 9.4": ["irascibility"], "14.7 5.4 0.1": ["aquisitions"], "3.0 10.6 17.6": ["bocks", "hydrothermally"], "6.9 6.1 14.4": ["purines"], "1.3 8.3 28.5": ["superphosphate"], "14.3 5.7 5.0": ["gigapixel"], "3.5 9.1 24.7": ["picante"], "2.7 12.1 7.0": ["redos"], "9.7 16.8 5.8": ["bureaucratization"], "7.0 4.4 8.0": ["unbacked"], "23.7 -5.9 0.1": ["cosies"], "9.2 7.3 5.7": ["crusing"], "7.2 18.1 3.7": ["scientologist"], "9.7 0.3 6.7": ["polyvalent"], "7.1 9.3 2.4": ["wrongfoot"], "7.7 3.4 13.4": ["ghz"], "14.7 -5.6 2.0": ["electrocardiograph"], "16.8 20.2 -1.7": ["atomizing"], "19.2 8.7 12.2": ["pantsed"], "6.6 8.4 14.7": ["membranous"], "-3.8 8.8 13.3": ["zoonosis"], "4.0 10.0 15.1": ["plyometric"], "-0.1 3.0 11.1": ["bute"], "10.8 12.7 5.4": ["xray"], "5.2 6.5 4.5": ["leds"], "1.7 10.9 4.4": ["fraced"], "6.3 15.9 11.4": ["crosspiece"], "-0.9 3.4 11.4": ["involution"], "12.1 26.8 10.1": ["satrap"], "7.8 -1.1 5.3": ["comprar"], "7.1 6.3 15.9": ["gerry"], "4.7 6.0 40.1": ["parmigiana"], "4.0 14.7 6.6": ["bouncebackability"], "-0.2 24.4 5.6": ["postition"], "-2.4 26.7 13.9": ["strikezone"], "9.5 4.5 20.1": ["longnecks"], "17.0 0.0 22.6": ["thermocol"], "5.8 8.9 1.4": ["windtunnel"], "3.8 -1.1 1.0": ["pourrait"], "-4.3 11.4 14.5": ["ulcerative"], "4.9 -0.4 8.9": ["toxicogenomics"], "14.2 6.5 5.5": ["photobooth"], "12.1 1.6 7.5": ["refurbs"], "17.4 11.1 12.7": ["corrugations"], "8.2 -1.6 -6.2": ["andd"], "17.4 8.6 6.6": ["spruikers"], "7.4 7.0 24.5": ["montane"], "5.1 7.3 9.5": ["miscounts"], "10.7 11.7 11.7": ["exosphere"], "0.7 6.5 5.2": ["redlight"], "13.9 13.4 11.9": ["spelunker"], "11.0 2.6 7.3": ["appx"], "11.8 5.8 16.3": ["mullions"], "9.8 7.3 10.8": ["schussing"], "2.2 -7.4 -1.5": ["beavailable"], "1.4 -5.1 9.3": ["meddai"], "8.4 10.4 12.2": ["khipu"], "13.1 19.9 7.5": ["captchas"], "7.9 -7.4 6.3": ["expectedto"], "-0.1 6.1 12.0": ["servlets"], "11.7 34.3 8.5": ["flyboys"], "18.7 9.1 4.5": ["whored"], "4.4 4.5 4.8": ["heatset"], "-5.5 10.7 9.6": ["underactive"], "-0.9 12.5 13.1": ["kaam"], "7.6 10.6 19.1": ["bearskins"], "13.1 14.2 19.5": ["axemen"], "8.2 3.2 7.8": ["decentralizes"], "10.6 14.7 18.7": ["footraces"], "14.5 9.5 15.3": ["hazardously"], "-2.3 7.0 8.9": ["certian"], "4.3 -5.4 11.8": ["uso"], "-0.4 2.4 7.0": ["estas"], "4.1 6.6 14.7": ["empresses"], "13.7 1.2 15.8": ["davenport"], "4.6 15.8 3.6": ["alles"], "-0.2 1.2 -2.4": ["subanalysis"], "11.2 23.1 16.0": ["resupplies"], "3.1 0.6 9.5": ["mme"], "3.4 -0.0 0.3": ["blueprinted"], "6.9 0.6 19.3": ["tricentennial"], "9.1 -0.1 20.3": ["homeys"], "28.2 22.6 13.8": ["outerspace"], "4.4 -5.3 10.1": ["upang"], "1.3 0.3 5.3": ["zah"], "5.9 2.5 10.3": ["vanessa"], "17.7 18.9 -0.4": ["renascent"], "0.5 10.8 12.7": ["unquenched"], "10.9 5.2 8.8": ["sme"], "-0.9 4.0 14.3": ["mourvedre"], "7.5 19.7 26.2": ["leafhoppers"], "9.1 4.5 32.4": ["kibbles"], "13.0 2.0 -1.9": ["suppling"], "3.1 7.9 21.1": ["manja"], "-7.1 6.9 3.4": ["courteousness"], "8.9 9.7 17.3": ["backshell"], "3.7 13.6 9.2": ["microsievert"], "-0.2 5.6 11.7": ["severability"], "2.9 10.2 13.0": ["overpack"], "-2.2 15.6 10.7": ["uphole"], "7.5 1.8 7.2": ["fois"], "4.4 -1.0 18.5": ["wristlet"], "5.7 5.3 8.5": ["trysting"], "-2.0 16.5 2.8": ["collocate"], "2.2 -1.6 -4.0": ["exhibtion"], "6.7 22.6 14.5": ["cocksucker"], "6.0 1.8 3.9": ["sx"], "-2.5 9.1 3.2": ["maxium"], "9.5 7.0 6.4": ["vlogger"], "4.1 19.4 11.9": ["fouler"], "10.6 16.0 2.4": ["prefiguring"], "-1.5 5.0 12.1": ["silking"], "3.9 20.7 12.5": ["bayanihan"], "4.1 3.5 -0.4": ["sef"], "2.7 16.3 3.6": ["easterner"], "-3.2 14.5 10.5": ["intercommunal"], "-4.0 17.1 6.2": ["elides"], "7.7 -1.4 46.3": ["scrod"], "7.4 4.6 19.8": ["tama"], "6.0 8.9 10.5": ["orthographic"], "5.8 21.8 6.2": ["actaully"], "-3.2 0.6 11.4": ["presynaptic"], "-6.5 0.5 3.2": ["thromboembolic"], "9.8 3.8 18.2": ["bali"], "-2.9 14.2 12.4": ["omer"], "6.0 23.0 13.1": ["kulaks"], "10.1 10.4 9.3": ["monopsony"], "-6.3 2.1 7.6": ["alteplase"], "-11.2 10.8 0.2": ["reffered"], "6.3 12.3 5.4": ["ambo"], "-3.2 6.5 0.4": ["excommunicates"], "5.2 13.9 2.2": ["baptizes"], "6.5 6.5 7.0": ["townhalls"], "14.8 2.6 11.3": ["bedstead"], "11.2 17.8 19.4": ["calcifying"], "0.8 -10.0 -2.8": ["particpated"], "4.2 -3.7 -1.1": ["comfirmed"], "-6.6 -0.9 2.5": ["mezz"], "-0.4 10.7 3.3": ["detectability"], "20.3 10.0 24.9": ["lilo"], "1.0 7.0 7.0": ["ulnar"], "3.2 24.3 8.2": ["detesting"], "6.0 -0.1 22.7": ["rosehip"], "12.7 23.0 18.8": ["revetments"], "19.7 15.6 16.6": ["currywurst"], "7.4 5.2 10.9": ["warbly"], "0.2 2.9 -6.0": ["andhas"], "6.6 1.6 9.9": ["cartonboard"], "-1.4 8.8 -5.2": ["adverted"], "2.9 -0.9 8.9": ["dueto"], "3.7 17.7 9.3": ["touchier"], "-4.0 6.1 15.7": ["lyme"], "7.6 4.6 11.2": ["poco"], "-4.6 8.9 9.9": ["noninfectious"], "5.0 14.7 11.6": ["turpitude"], "7.3 2.0 3.2": ["motown"], "6.7 6.6 6.7": ["medicament"], "0.9 26.7 -4.4": ["basij"], "-9.1 0.9 9.5": ["oenologist"], "4.0 13.2 3.7": ["redistributor"], "11.8 4.5 17.5": ["rakishly"], "15.2 7.4 34.5": ["sarnies"], "21.3 -2.1 0.8": ["entreprenuer"], "-3.3 12.9 10.8": ["desh"], "10.8 6.5 19.0": ["ketchups"], "-0.6 -4.5 -0.1": ["perfromance"], "12.8 6.8 24.8": ["chrysalises"], "8.0 9.9 14.5": ["oiks"], "8.5 7.3 21.6": ["freeters"], "1.9 17.9 6.6": ["intoxicates"], "8.2 21.7 7.2": ["brothas"], "3.7 9.6 8.6": ["lier"], "19.2 12.7 13.0": ["shadiest"], "9.6 8.0 7.8": ["equiptment"], "-3.3 -2.5 10.3": ["lyn"], "1.4 11.2 9.2": ["peevishness"], "2.0 3.4 6.9": ["microinverter"], "3.8 18.7 12.3": ["briber"], "7.4 12.5 5.0": ["neigbourhood"], "-6.8 3.2 10.4": ["varnam"], "6.0 10.9 15.4": ["haploid"], "-6.4 15.6 1.5": ["homocide"], "25.2 24.7 13.5": ["phantasm"], "6.1 9.4 11.9": ["footies"], "8.6 35.0 7.3": ["hegemonistic"], "7.8 20.2 7.5": ["discriminately"], "-1.3 10.4 12.0": ["ambitiousness"], "0.3 25.6 11.0": ["casuistry"], "8.2 18.9 9.3": ["conjoin"], "7.5 17.1 11.7": ["caudillos"], "2.1 7.8 14.7": ["likably"], "11.2 6.8 14.5": ["greenly"], "2.6 12.0 -0.7": ["handlings"], "10.1 9.0 16.5": ["chinkara"], "-4.0 -1.8 6.2": ["shool"], "4.2 3.4 15.6": ["kempt"], "13.4 15.1 42.2": ["damselfish"], "9.4 7.0 12.4": ["stiffeners"], "-6.4 4.0 5.2": ["pbs"], "12.2 5.0 16.8": ["oli"], "8.2 -2.8 -1.3": ["premarketing"], "-1.7 2.1 3.6": ["fluvoxamine"], "7.3 4.4 14.6": ["pitt"], "6.7 2.6 8.0": ["andere"], "9.7 -2.7 5.4": ["utive"], "-2.0 5.0 6.7": ["mimio"], "5.3 8.1 20.2": ["stratas"], "9.8 8.1 9.2": ["servomotor"], "6.5 3.0 7.6": ["choppily"], "6.6 15.9 5.8": ["penumbras"], "3.0 15.2 10.0": ["sonobuoy"], "21.7 14.3 23.2": ["glowstick"], "8.1 11.6 26.3": ["mucilage"], "1.3 17.7 4.8": ["darkhorses"], "4.7 3.8 1.0": ["unprescribed"], "5.7 11.6 -1.4": ["theyare"], "2.4 7.1 16.7": ["cuddler"], "-4.5 13.0 7.5": ["multifactor"], "-10.9 14.6 6.2": ["mitzva"], "10.4 5.9 28.7": ["cocker"], "-3.7 15.2 12.3": ["excellencies"], "4.0 8.0 -5.4": ["electrolyser"], "-2.4 5.5 22.9": ["microcystin"], "3.6 2.8 10.0": ["craftswoman"], "7.7 14.7 11.2": ["blub"], "0.6 8.7 0.5": ["rationalistic"], "3.9 -2.5 8.2": ["bookfair"], "3.3 17.2 13.0": ["antiphonal"], "0.8 14.4 -0.6": ["tensor"], "8.0 14.9 18.4": ["daggone"], "1.1 15.2 11.7": ["phagocytes"], "7.1 -0.1 6.4": ["gouaches"], "15.2 7.6 7.5": ["nanobubbles"], "13.8 1.8 3.0": ["entreprise"], "8.3 10.2 11.8": ["yahan"], "1.0 11.8 26.0": ["pelargoniums"], "-2.5 13.4 2.5": ["goodluck"], "6.2 8.5 4.7": ["mofussil"], "7.8 10.9 10.4": ["pelosi"], "3.2 12.1 11.7": ["uninflected"], "-3.2 5.1 -0.4": ["caravanned"], "2.5 2.7 10.1": ["polyurea"], "7.7 9.0 6.4": ["quadripartite"], "5.1 6.8 11.7": ["shopworker"], "1.1 4.9 3.8": ["triamcinolone"], "-6.3 2.2 2.4": ["varisty"], "-0.4 1.1 22.4": ["balik"], "12.5 1.9 4.6": ["databooks"], "-5.9 19.1 7.7": ["nominative"], "-0.4 -3.3 9.0": ["rescanned"], "7.6 41.2 21.5": ["antisubmarine"], "-0.6 24.2 8.8": ["dishonorably"], "-6.7 8.7 4.6": ["voriconazole"], "11.4 16.3 7.1": ["vacuousness"], "6.7 11.7 4.5": ["unprecented"], "20.4 25.3 12.9": ["boogieman"], "9.9 8.5 28.0": ["tabbies"], "14.5 10.2 15.5": ["rustics"], "6.3 -0.6 18.6": ["scrunchies"], "-4.3 17.9 9.9": ["micrometastases"], "3.9 -2.0 9.6": ["technikon"], "4.8 14.6 0.7": ["elision"], "-2.2 7.0 1.8": ["deputes"], "5.4 8.0 30.1": ["chummed"], "5.5 15.1 11.6": ["lucas"], "15.2 17.7 19.2": ["grunters"], "-3.0 8.5 3.4": ["fluence"], "12.6 13.6 20.9": ["echidnas"], "-1.3 2.6 6.8": ["victress"], "16.9 4.3 31.4": ["batfish"], "1.1 1.6 19.2": ["grosgrain"], "9.4 5.9 23.7": ["gallbladders"], "8.7 -3.2 19.7": ["shiang"], "7.1 12.8 13.7": ["translocate"], "9.7 8.7 25.4": ["counterman"], "10.4 20.6 9.7": ["maraud"], "5.6 5.5 15.7": ["chikan"], "-2.9 0.6 4.1": ["diluents"], "-1.5 -2.2 13.6": ["mula"], "9.8 10.8 14.7": ["epicentered"], "5.0 22.6 6.4": ["witchery"], "5.3 14.7 4.4": ["scrumbase"], "7.9 16.8 27.1": ["chytrid"], "5.1 13.3 5.4": ["outputted"], "4.3 0.7 3.6": ["haveto"], "10.1 12.0 -4.8": ["deutschmark"], "10.4 0.5 12.8": ["ritz"], "0.8 10.5 6.1": ["failback"], "8.8 11.1 10.2": ["gente"], "7.3 1.3 13.4": ["cara"], "11.8 24.6 26.3": ["goshawks"], "13.0 2.4 4.7": ["finnish"], "11.3 4.6 20.1": ["rusks"], "15.4 2.4 14.0": ["celeste"], "3.4 17.5 0.7": ["collectiveness"], "-0.7 8.0 19.4": ["cypermethrin"], "5.2 4.8 6.7": ["olmesartan"], "10.1 -7.3 -1.8": ["annoucing"], "17.0 8.0 8.3": ["accouterment"], "3.9 13.4 21.8": ["coppicing"], "12.7 9.5 18.6": ["rewrap"], "17.0 15.2 22.3": ["bkc"], "14.4 16.0 6.9": ["lasering"], "2.3 12.1 10.4": ["staphylococci"], "9.0 6.5 0.5": ["anticounterfeiting"], "0.7 11.4 8.4": ["pyo"], "-4.3 6.2 8.2": ["meiotic"], "7.8 2.9 18.9": ["snugged"], "-3.8 26.8 4.3": ["subjectivism"], "8.0 25.5 7.4": ["wiliness"], "2.1 4.7 11.6": ["kaolinite"], "12.4 18.7 9.8": ["unendingly"], "16.0 13.5 10.2": ["schmoes"], "3.1 -3.5 5.1": ["complet"], "-7.7 -2.3 -2.8": ["excutive"], "5.7 -4.9 2.4": ["tle"], "5.8 9.9 10.6": ["cary"], "2.9 2.0 -3.5": ["plantiff"], "7.5 5.9 3.0": ["specificially"], "-6.8 14.8 1.4": ["remediable"], "3.7 8.4 4.5": ["liberalises"], "1.3 9.9 11.2": ["glycation"], "11.5 13.6 12.9": ["tippler"], "6.6 9.4 10.0": ["slotman"], "6.1 3.8 18.8": ["dees"], "3.8 -3.9 -0.8": ["reserach"], "6.3 5.4 0.3": ["multisystem"], "2.5 5.4 1.7": ["thesauruses"], "9.9 18.8 8.2": ["damnably"], "3.9 9.0 10.0": ["nutting"], "-1.5 0.7 8.6": ["feasibilities"], "18.5 36.3 15.1": ["dementors"], "16.4 11.2 3.1": ["nobble"], "8.4 2.0 8.2": ["serigraph"], "4.4 6.8 7.1": ["swf"], "-0.4 2.0 -1.1": ["paliperidone"], "15.9 5.7 18.9": ["brigantine"], "3.0 22.3 9.5": ["schlemiel"], "11.2 6.7 20.0": ["grandiflora", "flageolet"], "4.1 2.6 7.6": ["tty"], "-0.7 6.6 3.0": ["liye"], "-8.9 5.5 0.1": ["dnf"], "8.2 9.4 -4.5": ["compatable"], "4.1 13.7 7.6": ["burkhas"], "3.6 21.7 12.2": ["circumlocution"], "-6.6 4.2 0.5": ["discrepencies"], "1.4 2.0 -4.1": ["appealled"], "5.0 -4.1 18.5": ["charmeuse"], "-0.9 10.7 4.0": ["telefax"], "-6.4 2.7 9.6": ["maturer"], "1.9 21.0 12.5": ["irreligion"], "6.4 13.5 29.4": ["seedheads"], "21.5 21.2 20.4": ["yetis"], "-5.1 0.1 4.1": ["retimed"], "9.0 12.7 6.3": ["emotively"], "-6.3 11.4 15.1": ["septoria"], "7.4 7.1 13.1": ["dabbawallas"], "-5.0 12.4 5.0": ["penciller"], "5.1 6.9 13.7": ["towpaths"], "-10.8 8.2 5.4": ["exegetical"], "-1.2 20.9 -0.1": ["goign"], "9.0 13.0 4.6": ["pronounceable"], "14.2 6.7 21.5": ["alehouse"], "13.3 2.2 5.1": ["easyjet"], "-1.3 2.1 -5.7": ["astatement"], "6.4 10.9 10.3": ["ministates"], "24.0 9.2 19.8": ["batwing"], "4.3 19.7 2.6": ["manuevering"], "8.8 6.5 12.4": ["chicas"], "-5.7 2.2 -1.7": ["anaesthesiologists"], "0.9 15.0 9.5": ["pullups"], "2.0 5.1 6.2": ["proxied"], "0.4 5.2 0.8": ["otelixizumab"], "-0.6 9.1 30.7": ["macroinvertebrates"], "5.7 7.9 7.9": ["mesmerises"], "2.6 24.8 7.1": ["changeless"], "-4.0 17.4 15.9": ["bello"], "7.8 2.1 8.5": ["chadar"], "1.7 7.9 6.9": ["reservationist"], "7.2 10.0 1.3": ["minisite"], "0.5 9.4 6.7": ["changeability"], "3.3 6.5 21.8": ["summerlike"], "-2.3 12.1 9.5": ["gpu"], "2.5 15.5 10.5": ["illogicality"], "13.9 6.0 13.9": ["nymphet"], "6.7 -2.3 23.9": ["corning"], "-3.6 9.5 8.7": ["medulloblastomas"], "4.3 9.8 13.7": ["calmodulin"], "12.0 8.4 9.7": ["tinsmith"], "10.3 21.1 18.1": ["sissified"], "10.1 2.8 19.6": ["corer"], "5.8 11.5 8.1": ["fugal"], "10.9 3.4 2.1": ["comfier"], "7.0 -0.3 35.0": ["triploid"], "6.8 10.0 16.3": ["neatnik"], "6.3 17.5 14.3": ["bloviation"], "1.8 5.1 12.8": ["pwede"], "4.4 17.0 12.6": ["unfriending"], "6.2 -4.7 5.7": ["preemed"], "7.0 5.0 21.8": ["plater"], "-4.0 4.5 10.8": ["myocytes"], "4.1 2.8 12.5": ["decriminalizes"], "9.7 16.9 18.3": ["jaguarundi"], "3.0 6.4 15.4": ["huskier"], "12.1 16.9 -2.6": ["albiet"], "5.1 3.1 33.5": ["chiffonade"], "13.3 3.7 8.9": ["lingua"], "21.7 6.2 21.9": ["moonbounce"], "4.7 8.5 9.2": ["kufi"], "5.8 16.9 1.8": ["outpassed"], "-5.1 6.0 5.3": ["journaled"], "7.6 5.9 16.4": ["potbellies"], "10.9 12.9 12.5": ["ghostbuster"], "5.0 11.8 13.5": ["amazin"], "4.8 1.0 11.4": ["foodstamps"], "12.4 11.1 7.8": ["palsied"], "-1.9 2.9 0.7": ["optionor"], "14.3 15.6 29.7": ["grizzle"], "21.6 16.4 20.6": ["moonbeams"], "3.9 6.2 10.1": ["sss"], "4.5 15.1 10.1": ["ribozymes"], "1.2 6.6 -3.5": ["recenty"], "16.6 -1.7 3.1": ["electic"], "2.0 2.4 5.4": ["nds"], "1.9 23.0 0.5": ["divisionism"], "1.0 5.1 33.6": ["lovage"], "6.3 18.4 5.5": ["deadset"], "-0.1 17.3 -1.6": ["recrudescence"], "12.9 8.1 11.3": ["sprog"], "10.3 3.9 0.9": ["apprently"], "8.3 5.4 0.8": ["vax"], "11.2 7.0 7.7": ["bilevel"], "6.6 3.7 40.6": ["underseasoned"], "17.6 11.5 29.9": ["vegie"], "-6.4 -2.0 18.1": ["nonvintage"], "1.4 4.2 7.3": ["resouces"], "6.2 11.2 36.9": ["dories"], "6.1 7.1 29.9": ["cartilaginous"], "6.3 1.7 16.7": ["rouler"], "4.2 8.0 13.9": ["gneisses"], "8.1 11.5 9.8": ["transversely"], "12.4 5.1 18.5": ["girths"], "3.8 28.6 10.6": ["syria"], "-1.8 3.4 2.7": ["bicifadine"], "11.7 10.3 15.5": ["cankles"], "-7.2 1.6 4.5": ["laryngectomy"], "-2.5 12.1 5.6": ["mycobacterial"], "4.1 9.0 6.8": ["rearwards"], "4.5 -1.9 0.3": ["deejayed"], "3.9 -0.5 13.7": ["recoating"], "2.7 10.1 8.7": ["physicochemical"], "7.1 16.0 11.3": ["graffito"], "4.6 0.5 16.4": ["lati"], "-2.0 5.0 10.5": ["consecutives"], "-8.5 8.6 2.9": ["explicates"], "13.0 9.4 -0.9": ["keyfob"], "19.8 34.1 22.1": ["golems"], "-3.9 12.0 1.2": ["forgotton"], "6.4 10.0 11.0": ["movieland"], "22.0 15.5 15.2": ["skyhook"], "4.6 4.1 -0.4": ["currenly"], "-12.1 12.1 6.3": ["solvability"], "5.3 23.3 -2.0": ["moslem"], "11.5 8.2 11.9": ["fumaroles"], "12.7 12.6 12.1": ["artbook"], "11.4 5.2 15.0": ["stereocilia"], "8.1 -0.1 3.1": ["hur"], "15.3 9.8 14.7": ["sportin"], "2.3 5.1 -0.7": ["spd"], "17.8 16.1 8.2": ["scroller"], "-7.4 17.5 5.8": ["presupposing"], "7.8 18.3 16.3": ["rotgut"], "4.5 0.5 2.7": ["membered"], "7.2 -3.9 19.5": ["tonners"], "5.8 6.1 9.9": ["megan"], "-0.6 9.8 2.2": ["frontliner"], "0.2 -7.6 12.6": ["loi"], "1.6 10.4 16.3": ["bloodflow"], "2.0 3.4 6.4": ["infl"], "16.1 4.9 16.6": ["resplendently"], "28.6 17.1 31.3": ["tusked"], "12.4 12.5 11.5": ["dowsed"], "7.2 -0.5 41.8": ["havarti"], "-2.5 12.5 10.7": ["distinctness"], "21.9 5.2 9.2": ["disgorges"], "14.9 -5.5 15.6": ["bakeoff"], "4.7 3.6 3.2": ["gradated"], "7.9 5.2 23.6": ["thalis"], "-0.4 8.4 -1.3": ["glomerulonephritis"], "4.0 13.2 -1.3": ["turbojet"], "-3.7 4.6 17.2": ["folates"], "-0.3 11.3 25.0": ["halva"], "3.4 -0.3 19.4": ["tup"], "3.0 1.6 13.1": ["tet", "cryoprecipitate"], "10.4 4.0 12.7": ["uprighted"], "-1.7 -1.6 5.0": ["vicariate"], "7.7 1.8 29.4": ["halloumi"], "3.6 9.7 10.8": ["knicked"], "8.4 12.5 10.4": ["detariffing"], "4.8 14.1 9.1": ["kinking"], "-8.7 14.4 6.8": ["psychotropics"], "-4.6 11.6 10.2": ["crosstabs"], "-1.7 14.5 7.8": ["suras"], "19.7 4.9 12.2": ["shedded"], "0.9 -1.1 3.4": ["khata"], "-1.0 17.8 2.6": ["speechmaker"], "1.0 11.6 6.8": ["prodrome"], "22.8 7.6 11.3": ["nickelodeon"], "-6.8 -3.1 9.5": ["mompreneurs"], "3.4 4.2 12.0": ["chiropractics"], "13.6 9.9 1.7": ["revivified"], "-5.8 4.9 2.6": ["operatory"], "-4.4 7.0 5.6": ["postop"], "3.0 5.1 6.0": ["parentally"], "-6.1 4.8 6.7": ["conciliar"], "5.8 11.0 9.2": ["sophisticatedly", "motorcylist"], "4.1 -0.5 -0.8": ["dalasis"], "5.5 12.5 32.3": ["kofta"], "2.6 14.8 13.9": ["regality"], "-7.3 -4.9 4.3": ["teleclasses"], "-0.1 10.2 16.0": ["dosha"], "13.5 17.8 4.2": ["analogously"], "12.6 11.9 9.9": ["haz"], "-4.2 8.4 8.9": ["valine"], "3.9 2.3 3.7": ["marcom"], "1.7 27.2 6.5": ["unipolarity"], "3.0 9.5 5.3": ["bawdier"], "5.6 11.1 16.2": ["subflooring"], "17.8 4.9 23.5": ["butterball"], "-0.9 16.4 4.8": ["hypocricy"], "6.7 5.8 -6.7": ["fooball"], "6.5 7.4 7.8": ["gabfests"], "-1.1 9.5 15.6": ["somatosensory"], "0.9 6.8 5.9": ["cytoskeletal"], "1.0 8.0 14.4": ["dynamin"], "9.8 3.7 8.0": ["unprinted"], "-1.1 9.9 8.8": ["trialer"], "4.4 4.0 22.7": ["sorbetto"], "6.4 4.2 4.6": ["cri"], "-0.2 12.5 6.6": ["unpublishable"], "13.4 5.5 10.2": ["nonslip"], "-2.4 21.0 0.1": ["unputdownable"], "-2.4 7.4 10.7": ["ischaemia"], "8.0 6.4 11.7": ["leftcenter"], "-8.3 7.4 2.2": ["catheterisation"], "-6.5 7.5 7.0": ["overassessed"], "6.4 8.4 20.0": ["necrophiliac"], "7.0 32.4 8.8": ["artilleries"], "15.1 10.6 18.8": ["furl"], "18.1 11.5 12.5": ["surfin"], "7.1 15.5 8.3": ["reflating"], "4.5 7.3 19.0": ["hotpots"], "6.8 8.1 18.2": ["nonpayers"], "6.1 4.8 9.6": ["ious"], "7.3 15.7 16.9": ["bodyline"], "2.7 17.3 2.5": ["bengal"], "-2.5 5.6 7.8": ["toolsy"], "-1.3 -2.6 11.1": ["oed"], "1.5 9.7 -0.6": ["desirably"], "17.4 12.2 6.1": ["niftier"], "15.4 27.5 6.1": ["airborn"], "2.9 0.7 12.5": ["tagatose"], "-3.2 6.1 6.5": ["psychoanalyzed"], "-2.8 -2.9 10.2": ["telemovies"], "1.6 7.3 1.6": ["immunobiology"], "6.1 21.4 0.4": ["stigmatises"], "7.6 -3.2 0.1": ["umming"], "1.5 18.5 18.7": ["overpair"], "5.2 9.6 12.7": ["andesitic"], "-2.0 3.4 -2.6": ["intraoral"], "17.2 -3.0 37.4": ["portabella"], "-9.9 5.8 4.3": ["neuroleptics"], "-1.6 5.0 1.9": ["mitigators"], "4.4 8.1 1.0": ["offi"], "0.7 8.8 1.8": ["bedoun"], "3.1 33.6 14.8": ["jutsu"], "4.7 4.2 26.9": ["gleaners"], "-3.3 16.4 5.2": ["learnable"], "3.1 10.0 19.9": ["rancidity"], "6.2 -0.9 7.7": ["reh"], "11.2 10.1 29.6": ["unmold"], "-0.7 8.1 7.8": ["nonrandomized"], "-3.4 19.5 17.6": ["backtalk"], "5.7 17.2 6.8": ["befooling"], "-3.9 3.8 9.6": ["hypermethylation"], "7.7 12.8 17.5": ["coppice"], "-7.6 6.1 8.0": ["leiomyosarcoma"], "19.0 11.8 12.0": ["omigod"], "18.7 15.2 17.0": ["shyt"], "11.2 0.7 17.3": ["bord"], "-2.8 15.2 9.5": ["meningiomas"], "-5.4 7.8 -0.6": ["mobilisers"], "2.0 1.2 7.7": ["hydrogeologic"], "4.1 3.8 16.1": ["inebriate"], "7.8 7.9 27.6": ["groats"], "12.4 2.2 10.4": ["sweetner"], "16.6 12.0 0.7": ["basketcase"], "4.7 26.6 12.3": ["adventurists"], "-7.9 5.0 2.6": ["codicils"], "17.8 21.0 9.6": ["privatizers"], "10.7 10.6 6.9": ["placatory"], "0.8 3.7 11.9": ["gingival"], "-2.6 16.7 4.3": ["stll"], "-0.4 4.1 8.6": ["pressue"], "5.7 19.8 -12.4": ["locatable"], "2.0 8.2 12.7": ["valencia"], "3.4 7.4 12.9": ["tumi"], "3.1 9.5 6.1": ["sparely"], "0.9 12.9 1.1": ["dooring"], "7.5 7.8 4.9": ["tous"], "-3.8 11.5 13.1": ["nonselective"], "-4.4 3.3 9.9": ["leflunomide"], "8.8 7.1 15.3": ["funksters"], "-2.4 9.6 11.6": ["raza"], "4.2 14.2 12.8": ["wisecracker"], "-5.3 4.2 10.7": ["alapana"], "8.4 6.2 12.4": ["dats"], "4.0 2.3 9.4": ["aqui"], "6.7 4.5 12.9": ["springboarded"], "4.4 21.5 15.3": ["canniness"], "8.0 0.3 1.5": ["releated"], "5.2 12.4 12.8": ["clothianidin"], "-3.9 3.7 0.5": ["antidiabetic"], "14.4 3.6 8.6": ["postboxes"], "-3.6 21.5 5.9": ["disapprobation"], "8.9 3.2 21.3": ["montana"], "1.3 14.2 17.5": ["moonset"], "-0.4 1.2 -1.9": ["seson"], "18.1 11.6 17.3": ["danglers"], "8.2 21.3 9.0": ["soundbyte"], "14.4 7.9 22.3": ["voyageur"], "4.6 11.3 9.0": ["carlos"], "11.0 10.0 18.3": ["finito"], "9.8 13.0 48.8": ["conchs"], "8.1 13.8 33.2": ["amphipods"], "15.8 12.6 11.0": ["hawt"], "-1.5 0.4 8.2": ["anticpated"], "-13.3 8.3 9.3": ["disenroll"], "-0.8 8.9 22.8": ["harbormasters"], "-3.4 9.7 8.5": ["incretin"], "1.9 20.4 9.0": ["denuclearising"], "13.5 5.8 10.0": ["sidesaddle"], "10.3 17.1 3.4": ["orating"], "16.0 15.4 15.0": ["palooka"], "12.9 11.0 7.5": ["dirigiste"], "5.6 -3.1 11.4": ["coatroom"], "4.5 17.9 12.7": ["meteorologically"], "4.8 12.1 5.2": ["underutilizing"], "-2.1 8.0 -1.8": ["forgiveable"], "-3.9 7.8 38.5": ["omakase"], "1.7 22.4 8.0": ["recognizability"], "8.7 12.5 29.7": ["mugwort"], "-1.2 12.2 13.4": ["eurusd"], "10.4 23.0 11.6": ["connives"], "7.2 -0.2 11.2": ["finca"], "7.1 8.4 28.3": ["bhaji"], "6.5 8.4 24.9": ["mauves"], "8.1 8.0 19.0": ["kuchen"], "8.9 5.6 30.8": ["rendang"], "8.2 13.1 51.2": ["bluefins"], "-9.7 5.2 7.2": ["perfectos"], "-3.0 4.9 0.4": ["valorization"], "-3.7 11.3 34.3": ["saugers"], "3.1 10.3 5.9": ["vernaculars"], "10.0 13.4 11.3": ["astrolabe"], "10.3 13.0 8.7": ["mindscape"], "11.1 28.8 26.8": ["cogongrass"], "4.0 -1.8 17.5": ["gymkhanas"], "3.9 19.7 2.6": ["stuggle"], "5.3 1.0 2.1": ["inluding"], "2.4 19.1 5.1": ["disaggregating"], "9.7 12.9 13.8": ["haversack"], "6.2 18.0 16.5": ["luffing"], "-1.7 16.5 5.0": ["pbuh"], "4.0 4.0 14.8": ["sugarhouses"], "5.5 12.8 12.7": ["variography"], "13.4 15.5 21.2": ["thwacks"], "0.4 7.0 10.4": ["zpizza"], "11.2 8.2 12.1": ["footprinting"], "4.6 2.6 15.2": ["softgel"], "4.8 3.8 7.6": ["alprostadil"], "2.0 27.0 2.7": ["codebreakers"], "7.1 9.6 4.8": ["remonstration"], "1.7 7.2 7.6": ["medullary"], "0.0 13.4 9.3": ["dislikable"], "2.3 11.5 15.2": ["ques"], "-16.8 -3.6 -8.9": ["medicolegal"], "5.1 12.3 11.0": ["tranquilly"], "6.2 2.7 -1.9": ["cust"], "4.0 3.3 -2.1": ["cyanoacrylate"], "-2.3 10.0 26.5": ["cholent"], "7.7 11.0 13.1": ["sitch"], "8.6 10.8 15.3": ["exurbia"], "-0.8 15.4 7.7": ["preferencing"], "8.9 7.5 22.6": ["freezeout"], "15.4 4.8 36.5": ["nopales"], "-8.4 1.5 9.5": ["ston"], "12.5 22.1 13.2": ["dystopias"], "8.0 5.4 16.5": ["furriers"], "4.4 13.4 10.8": ["renarrowing"], "0.2 3.2 4.8": ["conceptualizes"], "12.0 24.1 5.8": ["darkside"], "2.9 17.9 9.3": ["scooterist"], "9.5 -0.4 18.1": ["tufting"], "6.6 12.8 9.0": ["poors"], "15.2 8.3 -0.4": ["andits"], "-3.4 -0.3 18.2": ["cashspiel"], "1.6 8.1 8.6": ["mesoscale"], "5.7 12.5 9.4": ["youngin"], "-1.8 8.1 7.9": ["haptoglobin"], "-2.1 3.1 6.4": ["tetrahedrite"], "-2.5 5.3 9.2": ["prolificacy"], "-3.7 10.5 8.1": ["relection"], "-2.1 14.4 17.1": ["bowhunt"], "-2.5 5.2 15.5": ["girlishness"], "16.7 13.0 36.2": ["murrelet"], "11.0 13.8 15.8": ["whatcha"], "11.6 8.3 39.2": ["sopes"], "-2.3 11.3 9.9": ["trainability"], "5.8 5.1 1.6": ["electromyography"], "2.7 10.9 1.2": ["referenceable"], "-3.9 9.3 0.1": ["recharacterized"], "1.3 12.1 12.4": ["riflery"], "1.7 17.6 2.2": ["unpardonably"], "24.0 0.3 13.6": ["schleps"], "-0.5 14.7 5.9": ["infos"], "3.7 8.0 6.2": ["misclassify"], "5.9 18.2 13.0": ["gumshield"], "2.1 6.6 4.3": ["benzine"], "-8.9 2.3 3.2": ["restrictiveness"], "3.5 14.9 24.0": ["lowcountry"], "0.8 7.0 4.6": ["lly"], "3.9 16.4 6.6": ["inconsequence"], "9.9 6.2 8.0": ["overborrowed"], "6.1 5.6 11.8": ["pretested"], "-3.9 5.2 5.1": ["nonmarital"], "-0.2 13.0 3.7": ["tourmate"], "1.3 15.0 2.5": ["memorialised"], "5.7 3.6 14.7": ["videoke"], "29.8 -0.6 3.0": ["comapnies"], "4.7 8.2 24.5": ["greasiness"], "11.5 11.2 18.8": ["corrida"], "5.0 14.4 14.2": ["diverticula"], "0.6 -1.9 16.4": ["bunga"], "5.8 5.2 4.9": ["phial"], "1.7 3.2 2.4": ["ames"], "3.4 8.1 12.8": ["skidpad"], "9.7 18.6 16.4": ["tares"], "12.5 11.8 -2.6": ["beated"], "9.7 5.2 3.9": ["retakaful"], "4.5 10.8 13.7": ["refolding"], "10.9 23.5 23.3": ["mushiness"], "11.6 6.7 20.0": ["blake"], "3.2 6.4 6.1": ["teplizumab"], "-13.8 10.3 1.8": ["contributive"], "6.8 -2.9 19.7": ["halterneck"], "7.7 2.9 24.0": ["ovenproof"], "21.8 15.7 25.8": ["nibbler"], "-0.1 16.8 8.4": ["forceouts"], "17.2 15.7 30.1": ["wolfing"], "2.6 14.9 8.9": ["dyad"], "-2.2 10.1 8.5": ["fertigation"], "-3.4 0.9 7.2": ["housebreakings"], "-1.1 9.0 7.2": ["perchlorates"], "-4.1 0.6 -3.7": ["improvments"], "-3.0 25.7 8.6": ["hestitate"], "-3.3 7.0 20.5": ["nutritiously"], "4.2 4.3 5.4": ["aswaaq"], "5.4 12.1 18.3": ["desilt"], "11.3 8.7 7.2": ["jaunting"], "19.9 -4.4 10.0": ["oks"], "6.4 -1.4 16.8": ["packings"], "20.7 27.5 18.9": ["scimitars"], "3.5 10.6 10.6": ["feely"], "3.2 4.7 8.4": ["compensators"], "25.5 25.5 14.1": ["trebuchets"], "-5.7 20.1 5.1": ["demotivate"], "10.6 19.8 8.4": ["unbreathable"], "7.5 0.5 4.8": ["descried"], "-0.1 -0.2 9.9": ["pushrods"], "0.1 15.2 14.6": ["epizootic"], "3.0 26.7 2.9": ["koran"], "5.2 9.8 28.7": ["biryanis"], "5.0 4.3 -0.3": ["spirometer"], "1.1 4.9 1.1": ["judical"], "10.4 9.7 7.9": ["runover"], "-0.8 9.6 7.1": ["spammatory"], "0.7 1.8 14.2": ["saa"], "16.4 5.7 17.6": ["horsy"], "1.1 6.7 -5.3": ["baisas"], "4.3 14.5 8.5": ["sociobiology"], "-4.4 10.5 2.9": ["dicastery"], "6.4 11.4 15.6": ["uplegs"], "1.7 13.8 17.9": ["adulterant"], "2.2 11.3 22.4": ["kiteboard"], "15.2 14.9 22.2": ["katydid"], "2.0 7.6 9.8": ["novocaine"], "7.1 9.2 3.4": ["combustive"], "5.5 14.5 3.1": ["protostars"], "13.5 17.1 14.3": ["hosers"], "6.3 10.5 4.7": ["varicose"], "6.3 0.8 4.7": ["tomosynthesis"], "11.3 0.5 9.5": ["carbonless"], "-4.6 10.7 13.8": ["workups"], "-2.8 1.8 7.7": ["antifuse"], "2.1 14.5 6.7": ["sanyas"], "15.8 -1.5 15.6": ["plasticware"], "6.4 21.9 2.1": ["scientologists"], "4.5 10.9 -0.2": ["changemakers"], "3.8 11.4 2.4": ["derogative"], "-4.2 10.1 7.9": ["gaon"], "13.8 5.5 -6.8": ["assignors"], "6.3 4.4 0.4": ["codeless"], "9.1 9.6 32.7": ["pupusa"], "4.1 5.3 13.6": ["almshouse"], "5.8 1.4 10.6": ["homeloan"], "16.8 1.8 19.5": ["parterre"], "2.9 17.3 20.2": ["centremen"], "7.2 10.7 -2.7": ["correspondant"], "0.3 1.7 5.7": ["officiants"], "-3.2 6.9 3.4": ["pharmacotherapies"], "4.6 16.4 13.9": ["disfiguration"], "5.1 9.9 10.3": ["trehalose"], "3.4 13.4 6.4": ["fluxing"], "-2.3 7.4 9.0": ["blackbelt"], "4.0 8.5 36.8": ["ciguatera"], "12.0 6.4 13.3": ["alma"], "6.2 4.7 9.2": ["restaffing"], "3.0 2.0 4.3": ["erf"], "8.7 6.7 41.9": ["murres"], "6.0 22.3 14.9": ["survivalism"], "3.5 4.9 35.8": ["sautes"], "2.3 6.8 -2.1": ["contemporarily"], "14.9 9.2 3.3": ["railwayman"], "4.4 1.4 8.9": ["vocoders"], "9.8 18.1 8.7": ["nadal"], "11.7 16.4 0.2": ["highjacking"], "25.3 20.9 14.1": ["mamba"], "2.8 9.8 12.5": ["adobes"], "12.6 7.8 3.2": ["epitomy"], "0.6 12.5 7.0": ["conds"], "18.7 11.3 14.2": ["tradional"], "5.5 12.2 14.4": ["hasp"], "-0.8 11.4 4.0": ["dimerization"], "24.0 12.9 13.6": ["keiretsu"], "-3.2 -3.6 11.4": ["ced"], "13.2 11.0 33.4": ["boba"], "12.8 2.7 7.3": ["toping"], "1.4 4.6 7.1": ["vincent"], "0.1 8.6 11.0": ["collabos"], "11.2 30.8 22.9": ["powerup"], "-1.9 21.0 14.5": ["closeby"], "11.4 11.3 15.8": ["plentitude"], "6.9 13.0 16.6": ["plasmon"], "6.3 21.6 0.4": ["suborn"], "-0.5 11.2 2.1": ["datafeed"], "-0.9 0.2 2.3": ["interlayers"], "7.2 21.4 8.6": ["fulmination"], "-6.0 -6.9 -7.6": ["ombudswoman"], "-1.4 1.6 -4.1": ["perfom"], "14.5 8.7 11.5": ["amost"], "-8.0 1.8 3.4": ["defease"], "8.3 9.2 9.3": ["birmingham"], "10.4 7.8 3.2": ["fructified"], "8.9 19.5 5.5": ["bombastically"], "5.0 12.5 20.4": ["birded"], "11.2 5.9 11.0": ["tripple"], "9.1 27.7 8.9": ["nucular"], "5.9 0.8 8.9": ["ahora"], "9.7 15.0 6.1": ["cameraderie"], "10.3 4.1 6.1": ["nonexistant"], "11.7 13.7 5.9": ["electromagnetically"], "8.7 5.3 11.2": ["waiflike"], "1.1 0.7 2.7": ["relabelled"], "17.3 7.8 26.7": ["dashers"], "9.7 10.9 10.8": ["chorusing"], "1.5 -1.5 6.2": ["nota"], "4.7 12.8 15.9": ["mudders"], "5.7 23.0 1.0": ["unthought"], "9.0 4.2 27.1": ["megaships"], "-1.8 19.1 3.3": ["abusiveness"], "4.1 9.6 5.8": ["federative"], "5.4 11.9 6.1": ["germophobe"], "-1.9 3.2 4.4": ["programes"], "2.8 23.9 14.8": ["forechecks"], "23.2 15.9 14.3": ["fembot"], "-0.3 12.4 8.4": ["samarium"], "12.4 -3.0 -2.9": ["segement"], "0.0 34.6 -3.8": ["aggressed"], "-9.1 3.4 6.9": ["electively"], "16.6 0.2 0.1": ["sponser"], "-3.3 15.0 3.5": ["deputizes"], "2.5 4.7 18.2": ["clevis"], "-0.6 11.4 1.2": ["snowout"], "2.4 9.6 -1.8": ["rulling"], "9.9 14.8 12.6": ["buzkashi"], "-4.3 12.4 10.0": ["heterozygosity"], "12.0 4.3 17.6": ["softish"], "5.2 15.1 6.3": ["unadvisable"], "-6.6 8.6 11.8": ["upzoning"], "2.2 14.4 4.5": ["kaibiles"], "2.6 7.3 10.1": ["lateralled"], "9.9 8.3 10.5": ["pellucid"], "5.9 5.8 6.9": ["floorpan"], "7.6 5.2 27.5": ["laddu"], "8.8 12.0 15.4": ["powerbombed"], "16.0 8.7 16.8": ["overladen"], "0.6 15.4 7.8": ["abberation"], "13.1 4.3 9.9": ["baptistry"], "4.6 2.2 6.2": ["paralympians"], "-1.3 21.0 12.7": ["rideouts"], "4.3 12.9 18.0": ["iptables"], "23.2 6.1 4.5": ["beancounters"], "-0.5 11.0 8.8": ["bihar"], "7.1 11.9 4.4": ["hydrochloric"], "5.6 3.1 2.3": ["nanoparticulate"], "-0.6 2.4 16.9": ["ches"], "0.0 6.1 1.0": ["ximelagatran"], "12.6 2.3 11.3": ["chuntering"], "-4.3 6.9 -2.2": ["ketorolac"], "6.5 7.3 13.7": ["cherrypicking"], "10.0 5.0 -0.7": ["telecasters"], "7.8 12.5 7.5": ["seigniorage"], "18.9 18.4 9.4": ["soundwaves"], "-8.3 -5.9 5.8": ["nonet"], "-0.3 12.9 14.0": ["niners"], "-3.0 4.7 5.2": ["hematopoiesis"], "-5.5 13.5 9.3": ["reinjury"], "22.9 20.1 19.7": ["frenziedly"], "3.9 0.5 3.5": ["ladieswear"], "2.5 5.4 11.0": ["salars"], "6.9 6.3 19.1": ["ily"], "2.6 6.0 24.5": ["duns"], "3.2 1.4 7.5": ["rien"], "9.9 10.0 14.1": ["jolliest"], "-2.1 15.0 6.9": ["synchronizer"], "13.7 5.0 17.3": ["doos"], "18.4 10.1 16.7": ["ellipsoid"], "3.6 -4.2 15.8": ["sgnd"], "0.6 -0.1 6.5": ["ileostomy"], "7.2 4.2 19.3": ["washstand"], "-0.5 10.8 1.2": ["reassuming"], "5.6 14.2 5.7": ["admn"], "4.2 29.6 5.6": ["militarise"], "22.3 7.1 24.9": ["iceboxes"], "-1.7 -11.5 6.3": ["ining"], "1.6 0.0 5.0": ["nnn"], "9.0 -0.4 10.1": ["pfizer"], "-2.1 5.8 16.3": ["viniculture"], "0.6 14.5 20.0": ["blackpowder"], "-2.6 5.5 8.2": ["parallelize"], "8.6 9.8 6.4": ["distractible"], "1.8 5.5 26.3": ["tanagers"], "14.1 19.4 1.0": ["inveighing"], "10.9 11.1 4.4": ["remaindered"], "2.3 17.0 2.5": ["extrememly"], "1.2 -2.7 4.0": ["contractural"], "0.3 4.3 4.4": ["precalculus"], "11.1 11.1 13.7": ["multisourcing"], "11.7 3.3 21.9": ["drywallers"], "14.8 19.1 26.5": ["slimey"], "5.2 10.7 12.9": ["photosphere"], "27.4 7.8 6.3": ["jackhammered"], "3.5 11.8 14.6": ["ceremonials"], "7.0 6.5 10.2": ["yuans"], "1.2 8.9 7.2": ["exergames"], "6.0 12.3 10.3": ["swapper"], "9.6 4.5 3.5": ["marke"], "8.6 7.2 24.3": ["flakier"], "5.8 -2.1 13.6": ["centrifuged"], "9.1 10.8 9.4": ["polymorphous"], "14.0 -1.0 12.1": ["alta"], "-1.6 -4.1 -0.1": ["lpi"], "0.1 6.4 2.1": ["blabs"], "10.1 2.2 17.3": ["creperie"], "10.3 12.2 23.1": ["discolour"], "10.0 14.4 -0.6": ["immolate"], "1.1 8.7 13.3": ["dojos"], "6.2 9.7 8.5": ["switchbox"], "-6.0 7.2 -1.5": ["xxxxxx"], "-10.3 3.7 4.4": ["dyspareunia"], "18.0 19.7 21.7": ["zodiacs"], "1.8 20.5 7.9": ["coronate"], "-2.8 10.1 5.2": ["soundchecks"], "17.4 12.2 2.9": ["mimick"], "9.2 7.0 12.3": ["watercooling"], "6.2 1.8 23.2": ["saltbox"], "12.3 14.8 5.9": ["gvt"], "-2.2 4.9 4.0": ["availibility"], "5.1 19.3 6.0": ["subversions"], "-0.3 7.1 1.5": ["misfueling"], "3.3 0.2 0.8": ["pepping"], "-1.2 11.2 15.0": ["topo"], "-0.6 9.7 3.5": ["tecarfarin"], "-1.2 17.5 8.4": ["talkativeness"], "4.0 6.4 9.1": ["melodiously"], "11.1 14.3 24.6": ["lariats"], "6.6 4.7 6.6": ["pumpsets"], "12.0 8.1 5.6": ["simples"], "4.5 0.7 6.6": ["cochairmen"], "-3.6 12.4 6.1": ["chemobrain"], "16.3 -1.5 17.4": ["quadrille"], "13.9 16.3 10.9": ["jackknifing"], "-3.0 8.0 7.2": ["ayacut"], "-2.3 2.0 12.0": ["kaso"], "10.9 19.6 9.9": ["everybodys"], "7.9 13.9 7.3": ["multiform"], "4.9 6.0 13.7": ["jesse"], "2.3 1.6 1.0": ["unstimulated"], "10.3 7.6 9.5": ["moet"], "10.1 5.8 -0.1": ["deconsolidate"], "10.3 2.6 12.9": ["celesta"], "8.3 8.0 10.2": ["headgears"], "14.9 2.8 9.8": ["glamourpuss"], "3.4 12.2 16.0": ["debark"], "14.6 -3.7 15.5": ["frizzed"], "21.1 4.0 6.5": ["bancassurer"], "1.3 7.5 5.4": ["leage"], "5.0 8.3 5.4": ["repossesses"], "-3.2 8.3 5.4": ["adenoviral"], "10.0 11.7 5.3": ["transmutes"], "-0.3 18.1 1.6": ["niether"], "13.1 44.0 18.4": ["zerg"], "-6.3 8.1 3.3": ["eplerenone"], "-1.5 8.2 -0.1": ["replanning"], "18.8 7.8 31.8": ["plesiosaurs"], "3.0 9.5 10.0": ["leftside"], "19.6 8.7 5.6": ["fullscale"], "6.4 11.8 5.2": ["schon"], "0.6 2.0 17.6": ["granulate"], "21.5 10.9 7.9": ["purloining"], "-7.6 16.1 4.7": ["succinctness"], "2.9 -0.3 16.9": ["shannon"], "15.8 8.9 15.2": ["turk"], "-1.7 11.8 5.9": ["byt"], "5.9 2.4 8.7": ["biog"], "-0.2 6.5 8.9": ["forwardly"], "8.1 4.6 17.9": ["acidophilus"], "5.7 8.7 14.8": ["stockpicker"], "7.4 1.4 41.1": ["lardo"], "8.6 1.9 3.1": ["cinematheque"], "21.3 12.3 22.3": ["trapezoids"], "14.1 13.2 14.3": ["auguries"], "-4.0 2.1 4.4": ["reselected"], "4.9 -2.8 3.6": ["spl"], "10.1 8.0 6.7": ["scootering"], "-5.7 9.0 10.1": ["allelic"], "-0.4 -0.5 16.2": ["phytosterol"], "9.0 6.9 1.7": ["firesuits"], "7.1 26.2 8.9": ["nutroots"], "12.7 -2.8 7.2": ["jaar"], "-5.8 9.3 12.4": ["improvs"], "-3.4 5.3 12.0": ["dramedies"], "-2.4 5.1 0.6": ["guanfacine"], "-4.1 1.1 11.4": ["distributaries"], "-5.1 3.5 8.2": ["eed"], "-0.4 7.8 8.9": ["mommyhood"], "1.8 12.0 5.0": ["pyromania"], "23.3 7.8 4.0": ["superbrand"], "3.7 -3.5 6.2": ["replacment"], "10.2 1.5 3.9": ["cottoning"], "13.6 5.4 18.1": ["titanosaur"], "-1.1 3.6 8.6": ["toothbrushing"], "-3.1 1.6 2.3": ["diwan"], "-9.0 1.2 4.5": ["newswriting"], "1.4 12.9 21.0": ["blackbucks"], "6.7 18.1 8.5": ["noisiness"], "10.2 -5.5 49.4": ["escolar"], "12.1 6.8 16.1": ["whimsies"], "7.2 24.6 3.5": ["minorityism"], "2.4 2.9 5.7": ["isomerization"], "3.4 7.3 1.3": ["multiengine"], "7.8 4.7 14.7": ["gatorade"], "-5.4 4.1 7.2": ["nasopharyngeal"], "-6.8 0.8 5.2": ["ges"], "4.1 4.6 14.8": ["worrisomely"], "10.5 4.3 11.9": ["barer"], "12.2 7.9 5.2": ["nutmegging"], "14.6 4.6 3.4": ["kurus"], "-1.4 3.5 0.3": ["bodyshops"], "15.3 18.7 20.9": ["jousters"], "10.1 35.6 9.6": ["griefing"], "6.4 8.7 15.3": ["shuk"], "8.5 -4.5 -0.2": ["mondiale"], "9.0 14.6 4.0": ["imbedding"], "3.0 15.4 12.1": ["wristshot"], "5.4 2.9 8.4": ["subsegments"], "-1.0 16.1 1.5": ["inheres"], "-9.0 5.3 7.5": ["postulants"], "-2.6 11.3 2.4": ["infarcts"], "21.7 10.7 19.4": ["bellyflop"], "12.5 22.1 13.7": ["pestilential"], "11.6 18.7 10.4": ["graspable"], "12.1 21.1 10.4": ["puckishly"], "7.9 23.8 13.4": ["taxer"], "7.3 2.7 8.8": ["winsomely"], "4.8 7.4 6.1": ["metallicity"], "8.8 -0.4 27.6": ["choy"], "0.4 14.4 5.9": ["outstaying"], "-5.7 12.3 6.2": ["premalignant"], "11.9 11.0 5.1": ["eir"], "1.2 -5.1 17.5": ["sumer"], "13.7 2.0 14.1": ["accesories"], "-7.9 23.7 0.0": ["persecutory"], "-1.0 9.9 5.4": ["barnburners"], "4.1 3.9 19.8": ["ferrules"], "7.1 11.9 12.5": ["woofs"], "-5.8 14.4 1.1": ["ecumenically"], "1.1 3.6 2.1": ["cobas"], "9.9 4.0 5.4": ["playspace"], "3.8 11.6 7.1": ["yajna"], "-2.6 0.2 8.5": ["haircolor"], "9.3 3.4 3.8": ["palindromic"], "-0.3 16.5 9.8": ["orienteers"], "-3.1 10.2 -0.1": ["revascularisation"], "10.7 -3.8 4.8": ["anche"], "9.9 14.7 15.2": ["purgatorial"], "2.7 3.1 -2.3": ["bookstalls"], "5.1 4.0 39.7": ["sirloins"], "11.3 0.2 13.2": ["lidding"], "15.0 26.2 6.7": ["godhood"], "2.5 -1.4 4.4": ["rancheras"], "5.6 1.0 8.8": ["ambulant"], "13.2 -3.6 1.9": ["aproximately"], "0.8 -1.6 -11.0": ["represenative"], "19.8 7.5 24.4": ["jalebi"], "-1.7 13.2 0.4": ["longrange"], "13.8 7.6 11.5": ["diagrammatic"], "15.6 5.7 9.1": ["chinadotcom"], "18.8 12.8 11.8": ["plexiglas"], "-4.6 -4.0 1.4": ["wlll"], "14.4 6.0 13.2": ["rhapsodies"], "-2.0 -0.5 -1.3": ["sexologists"], "4.0 36.9 15.5": ["deathmatches"], "-4.9 -2.3 6.8": ["staf"], "16.0 15.0 23.0": ["handsaws"], "7.0 12.3 4.5": ["antiracist"], "9.6 8.4 2.0": ["moire"], "7.5 10.9 2.9": ["prizefights"], "6.4 7.4 18.2": ["dou"], "6.6 8.1 18.5": ["hybridizers"], "-2.5 -0.9 8.8": ["supersoft"], "-7.1 13.0 8.5": ["nolle"], "8.5 15.0 7.5": ["screencap"], "0.2 9.6 16.1": ["hardscapes"], "19.6 13.7 19.4": ["clinks"], "-3.4 6.5 5.7": ["gemologists"], "16.5 -1.2 -0.3": ["multiproduct"], "1.9 8.8 4.4": ["oline"], "14.3 16.5 6.7": ["repulsively"], "1.1 6.2 6.5": ["midblock"], "-9.2 8.6 5.1": ["pneumonectomy"], "3.1 24.1 25.5": ["longbows"], "5.3 -6.3 9.3": ["babywear"], "-2.2 6.6 28.1": ["overlimit"], "6.3 17.5 10.9": ["deforest"], "9.8 7.1 17.1": ["heathy"], "-0.6 3.8 3.7": ["altoist"], "12.6 14.2 8.2": ["muscularly"], "-4.3 12.4 7.0": ["camporee"], "-3.4 4.6 8.5": ["epigrammatic"], "-1.1 8.1 10.2": ["exocytosis"], "3.2 10.1 9.8": ["chowky"], "0.6 2.7 13.9": ["iti"], "5.5 19.0 6.8": ["stovetops"], "-5.2 18.4 1.9": ["physcial"], "0.6 6.3 8.2": ["pseudogenes"], "16.2 7.9 11.8": ["thankyouverymuch"], "8.5 5.6 3.3": ["conjointly"], "1.5 25.5 16.7": ["sonobuoys"], "3.6 15.2 18.8": ["biofouling"], "7.6 14.6 10.1": ["textbox"], "4.8 11.5 28.9": ["pachysandra"], "11.0 18.1 14.6": ["jaggedly"], "7.3 15.2 15.3": ["aconite"], "0.4 16.0 10.5": ["cogitation"], "11.3 3.6 13.5": ["perkily"], "14.1 4.8 21.7": ["shui"], "7.9 -1.9 18.2": ["fect"], "13.3 8.4 12.2": ["americas"], "-0.1 -1.6 9.1": ["apts"], "2.3 5.5 16.5": ["corundum", "baru"], "11.0 15.1 5.9": ["inaudibly"], "13.3 10.8 49.0": ["hogfish"], "1.0 0.8 7.9": ["concatenated"], "9.8 -1.7 -7.4": ["groupe"], "3.4 21.1 13.8": ["compartmented"], "15.0 -7.4 7.4": ["inaugral"], "8.1 8.8 8.7": ["sportster"], "-5.9 4.2 0.8": ["achieveable"], "22.4 13.3 9.7": ["gawped"], "-3.1 10.2 1.1": ["flattrack"], "4.0 6.9 11.4": ["televiewers"], "-0.5 15.4 3.5": ["lameduck"], "-7.2 11.3 1.0": ["streptococcal"], "-3.2 5.4 7.1": ["osteoblast"], "4.7 5.7 6.8": ["geochemists"], "-3.8 5.2 2.4": ["plurilateral"], "3.7 11.4 13.9": ["formrusmcsgt"], "-0.3 18.1 12.3": ["wheather"], "-1.9 11.4 11.8": ["cartilages"], "7.0 9.2 17.2": ["mina"], "8.6 7.4 9.6": ["pornos"], "6.1 1.7 -1.1": ["cyberlaw"], "10.0 12.3 13.7": ["snogs"], "5.8 1.9 20.7": ["qipao"], "4.9 6.8 38.0": ["panzanella"], "-1.6 1.4 12.8": ["agroecology"], "13.0 6.3 8.2": ["firedog"], "-0.2 5.0 3.0": ["valvular"], "2.9 5.0 15.4": ["madre"], "8.6 0.6 3.3": ["crosslinked"], "2.3 5.7 13.8": ["inhibitive"], "1.4 7.2 9.1": ["vive"], "-1.5 16.0 1.9": ["uncorrupt"], "1.7 6.0 14.0": ["stopbank"], "10.6 19.4 28.4": ["lovebugs"], "4.3 -1.6 9.5": ["theorbo"], "9.9 0.8 6.1": ["horology"], "4.6 11.4 15.2": ["yenta"], "0.8 26.2 -3.0": ["nazism"], "1.4 2.4 1.9": ["tema"], "12.8 2.4 13.9": ["tousle"], "-0.3 3.7 12.4": ["entrymate"], "5.1 5.2 23.2": ["motoryacht"], "-4.9 8.2 7.9": ["catecholamine"], "7.1 18.5 5.6": ["obj"], "1.2 13.1 6.2": ["probaby"], "11.7 11.2 13.8": ["multibagger"], "14.4 12.6 18.8": ["dockland"], "-0.1 17.4 15.7": ["localhost"], "-4.6 4.4 6.0": ["cliental"], "9.1 2.4 21.7": ["ruffly"], "11.3 7.0 18.3": ["appy"], "0.3 13.9 9.8": ["becos"], "-11.4 15.4 1.6": ["marja"], "-2.8 9.4 -4.0": ["wherabouts"], "5.7 8.6 15.6": ["kom"], "11.0 16.0 7.1": ["luchadores"], "2.6 10.2 14.0": ["transvestism"], "-3.5 6.4 21.2": ["meads"], "10.1 20.4 6.7": ["debtholder"], "7.6 9.9 11.9": ["rotators"], "5.3 5.8 8.2": ["behavorial"], "-0.6 12.4 0.4": ["critisism"], "6.6 7.5 12.7": ["breadwinning"], "15.8 19.2 30.6": ["flatworms"], "-3.9 19.6 11.3": ["amanuensis"], "17.5 6.1 7.7": ["woot"], "3.1 4.0 20.4": ["puso"], "-0.5 8.9 3.1": ["indivdual"], "7.3 1.5 13.1": ["diatomite"], "5.1 6.9 -0.7": ["wasl"], "-2.9 0.4 20.6": ["gris"], "-2.8 6.8 3.6": ["amnio"], "-2.2 0.0 12.1": ["songkok"], "4.6 19.7 11.2": ["taze"], "-1.4 7.6 8.9": ["vascularity"], "8.0 13.2 5.9": ["modi"], "15.6 7.2 14.3": ["packrats"], "7.1 18.2 12.1": ["obliquity"], "-8.5 10.3 2.3": ["demurrers"], "-2.2 8.0 6.2": ["dormie"], "0.6 2.8 10.1": ["doripenem"], "12.3 12.7 2.6": ["zettabyte"], "-3.5 6.4 4.3": ["implementors"], "14.8 -4.2 7.6": ["unbolting"], "1.3 4.8 13.0": ["neckpieces"], "7.4 3.9 5.4": ["wurden"], "3.0 11.0 18.8": ["shoetops"], "4.3 2.9 2.0": ["beim"], "10.8 12.9 22.7": ["laughin"], "15.5 4.7 22.5": ["faience"], "6.9 9.7 10.0": ["fluorocarbons"], "17.8 13.6 9.7": ["nanorobots"], "3.2 14.8 16.1": ["brahmin"], "5.5 3.7 1.2": ["mdn"], "-2.1 7.6 7.1": ["bluesier"], "9.2 10.8 -0.1": ["anaesthetized"], "5.2 4.1 6.4": ["tiempo"], "11.7 12.1 10.1": ["theri"], "19.7 5.7 7.9": ["sniffily"], "-7.0 10.2 23.2": ["nebbiolo"], "3.4 10.6 8.6": ["interleukins"], "19.8 13.1 2.5": ["microprocessing"], "2.9 11.2 7.9": ["lastnight"], "14.7 6.9 23.1": ["holt"], "6.0 7.4 7.9": ["freecycle"], "7.3 6.5 15.9": ["moringa"], "8.4 11.1 27.5": ["rasam"], "2.8 17.8 5.9": ["blest"], "3.4 25.7 10.0": ["ballistically"], "14.8 14.1 9.0": ["reincarnating"], "13.9 4.4 14.6": ["loooove"], "-0.9 9.5 5.5": ["lacunas"], "8.5 16.8 10.9": ["paternalist"], "18.4 4.2 10.3": ["toay"], "2.6 5.2 4.2": ["notate"], "28.9 30.5 18.1": ["insectoid"], "8.0 -2.7 4.4": ["bodycare"], "7.5 5.6 17.5": ["psittacosis"], "9.6 6.3 14.9": ["halftone"], "13.4 4.3 -2.3": ["turbofans"], "9.7 2.2 4.7": ["groundsharing"], "-2.8 8.1 6.3": ["clocker"], "-3.1 5.8 8.7": ["penghulu"], "3.7 7.9 5.4": ["guideways"], "4.4 17.9 13.0": ["haraam"], "6.2 1.2 0.7": ["frankfurt"], "-2.4 7.6 1.3": ["cimetidine"], "-0.5 6.0 5.0": ["unevaluated"], "14.1 12.0 8.9": ["oif"], "0.0 3.8 5.1": ["cytometry"], "2.2 8.2 2.6": ["stuggled"], "9.7 5.5 3.3": ["almorexant"], "-8.3 -3.5 14.1": ["phenylbutazone"], "-1.6 -7.2 10.9": ["wirespeed"], "11.8 8.2 8.1": ["supermum"], "-10.6 -1.0 13.6": ["truancies"], "1.1 9.1 8.5": ["undercovered"], "16.0 11.5 14.4": ["binnacle"], "9.4 2.1 11.4": ["noncarbonated"], "15.2 7.1 24.5": ["spritzers"], "12.8 6.9 10.5": ["dilapidating"], "9.2 -0.2 2.7": ["policosanol"], "1.4 19.8 20.7": ["northerlies"], "17.3 4.2 17.5": ["inlayed"], "3.2 0.3 24.7": ["gallo"], "0.8 9.1 7.1": ["dpb"], "5.6 8.2 7.9": ["configs"], "10.6 16.5 12.3": ["stupefy"], "7.5 14.6 9.4": ["headbang"], "3.4 2.8 0.4": ["strenghtened"], "3.4 16.4 9.3": ["roader"], "-0.2 4.5 5.5": ["decares"], "10.0 0.7 1.6": ["fresheners"], "-3.7 8.2 28.0": ["gabi"], "-6.9 11.2 2.7": ["bridgeable"], "2.1 10.4 8.2": ["pellagra"], "14.9 7.9 -0.2": ["purveys"], "-1.2 3.2 12.2": ["mtu"], "-2.9 17.8 0.2": ["rouser"], "4.2 1.3 7.2": ["tris"], "1.6 16.0 3.1": ["amnesic"], "8.4 31.8 2.2": ["lawlessly"], "-6.8 3.0 6.6": ["topicals"], "10.0 11.8 17.1": ["alexander"], "14.7 3.2 2.8": ["seamier"], "13.2 13.5 18.4": ["flation"], "5.4 9.9 9.1": ["hans"], "9.7 4.4 9.9": ["boogieing"], "-1.1 5.5 3.2": ["superhits"], "-0.9 5.0 12.0": ["gobyerno"], "0.7 6.5 7.4": ["supervening"], "7.4 9.4 2.1": ["steepens"], "-0.5 8.6 1.3": ["dissociates"], "5.4 5.8 13.0": ["vaqueros"], "16.0 3.8 13.8": ["fon"], "6.4 4.0 27.4": ["rojak"], "4.1 17.2 9.4": ["mukhiya"], "2.1 11.0 -8.5": ["abetter"], "14.7 -1.1 10.9": ["wendy"], "9.3 23.6 5.7": ["corrupter"], "11.2 13.7 8.9": ["limitlessly"], "-2.7 15.3 12.1": ["propitiation"], "-2.2 14.7 5.5": ["counterfoil"], "3.3 1.7 1.7": ["uc"], "10.0 13.5 10.1": ["sublimates"], "0.1 21.2 12.0": ["essentialism"], "6.3 3.0 5.3": ["glaceau"], "-3.8 3.4 0.3": ["lurasidone"], "4.7 3.9 -1.2": ["unretouched"], "-7.5 0.4 2.7": ["ammended"], "16.3 13.9 16.5": ["oceanliner"], "6.0 3.6 5.8": ["pv"], "11.2 13.0 12.3": ["skronk"], "12.4 13.4 16.9": ["fellah"], "8.5 6.6 8.4": ["buil"], "-6.9 10.5 6.4": ["covariate"], "0.7 -2.5 16.4": ["cuvee"], "3.6 -3.4 2.5": ["sheduled"], "16.0 13.6 9.4": ["puissance"], "10.0 20.0 11.6": ["koan"], "7.6 0.7 5.0": ["electroacoustic"], "9.1 5.8 5.9": ["fuser"], "11.3 15.5 11.7": ["wingsuit"], "12.3 14.2 15.6": ["dreamiest"], "-9.1 15.8 11.8": ["overtrain"], "7.8 13.4 22.3": ["serrations"], "16.1 22.6 18.2": ["unstopped"], "8.9 7.1 4.3": ["trustmark"], "4.2 3.7 15.6": ["plantable"], "18.1 15.9 18.8": ["hucking"], "-2.5 21.7 1.7": ["coalitional"], "15.0 5.8 15.6": ["tranquillised"], "8.4 18.0 10.1": ["otherside"], "-6.5 8.7 10.5": ["crosspoint"], "6.5 6.4 6.2": ["typesetters"], "1.7 7.1 7.1": ["protrade"], "-4.4 -5.8 7.4": ["dw"], "5.4 -0.8 12.3": ["isobutane"], "12.7 3.6 27.9": ["paletas"], "4.6 -3.0 17.5": ["sashed"], "4.8 10.7 9.0": ["geniune"], "6.3 11.0 4.4": ["geocoded"], "4.3 10.1 35.7": ["godwits"], "-2.4 24.6 9.0": ["stovepiped"], "14.5 1.5 32.4": ["yummies"], "3.6 6.5 12.2": ["tarping"], "8.8 -3.8 12.2": ["smallscreen"], "6.8 1.0 -1.5": ["higly"], "-8.4 8.4 10.4": ["discretional"], "15.5 10.4 24.2": ["waterscape"], "4.3 3.4 10.8": ["mahal"], "17.3 18.3 33.2": ["swallowtail"], "2.6 7.0 1.0": ["unforthcoming"], "0.2 8.6 -3.7": ["intergrity"], "2.5 -0.3 1.8": ["etv"], "3.7 17.1 0.1": ["oncolytic"], "-11.5 0.2 -0.6": ["coadministration"], "0.7 4.3 9.4": ["landcare"], "3.7 13.2 26.2": ["freshies"], "-1.1 0.5 6.0": ["cysteamine"], "-4.7 4.8 9.4": ["clomiphene"], "1.1 10.3 13.6": ["pedicurist"], "4.2 8.8 6.4": ["confederal"], "5.8 2.5 16.2": ["mento"], "4.6 7.7 9.3": ["aliment"], "12.8 -2.1 -4.2": ["servies"], "6.8 15.9 9.1": ["poisonously"], "10.5 -4.0 19.2": ["diam"], "10.1 3.4 -2.3": ["bne"], "6.2 23.0 4.3": ["rivalrous"], "1.5 15.9 10.7": ["hazarded"], "11.7 11.8 14.7": ["airballing"], "2.9 2.8 6.8": ["butterflyer"], "0.1 -1.2 5.9": ["normotensive"], "-1.2 30.8 6.6": ["narcoterrorism"], "2.7 -0.0 1.3": ["monring"], "6.4 8.7 9.6": ["darwin"], "10.1 9.8 5.6": ["bcs"], "26.5 22.3 25.6": ["furballs"], "-4.1 7.0 4.9": ["permissibly"], "-10.0 7.5 4.5": ["superinfection"], "-2.3 2.7 4.8": ["poitns"], "4.4 5.9 6.2": ["insitu"], "0.6 15.3 17.1": ["uppish"], "6.4 15.0 4.0": ["blatently"], "2.4 6.0 12.7": ["dise"], "19.1 6.7 1.5": ["gazump"], "5.2 3.6 -0.4": ["desmoteplase"], "8.8 24.8 16.5": ["bullseyes"], "4.0 -0.3 1.0": ["scandalising"], "6.8 7.1 26.2": ["unworked"], "22.4 14.0 11.6": ["moonwalker"], "6.5 5.4 25.4": ["babka"], "14.2 1.5 14.8": ["sunkissed"], "11.8 15.1 5.4": ["transmogrification"], "12.6 -1.8 9.3": ["twelvefold"], "-6.3 8.9 4.2": ["tightend"], "18.7 20.7 14.0": ["coopetition"], "16.7 10.6 7.6": ["unharnessed"], "-4.7 10.3 5.8": ["procyclical"], "17.6 14.9 22.1": ["clifftops"], "2.1 20.1 10.5": ["prosopagnosia"], "3.8 25.8 15.1": ["clansman"], "11.0 8.0 17.0": ["hippiedom"], "1.6 6.7 5.5": ["siloxane"], "-8.4 13.9 -0.1": ["postpetition"], "5.0 -8.3 -1.8": ["nder"], "-3.5 4.5 12.9": ["tamariki"], "-0.1 8.7 6.0": ["newsquestions"], "4.1 7.9 7.9": ["carful"], "0.4 4.0 1.2": ["puttable"], "-6.0 19.9 8.2": ["sadhana"], "0.7 9.1 3.7": ["allodynia"], "1.3 -1.4 6.0": ["micronized", "lasofoxifene"], "7.9 11.2 12.4": ["pagerank"], "7.5 9.7 9.1": ["thata"], "1.4 8.6 4.4": ["borstal"], "-1.9 8.8 7.5": ["stimpmeter"], "7.3 18.6 5.3": ["camerman"], "-5.1 5.5 -0.2": ["thermometry"], "4.3 19.2 3.8": ["vexations"], "16.0 4.6 12.6": ["slickened"], "9.8 11.4 5.5": ["dudgeon"], "7.3 -5.5 1.5": ["secondees"], "5.5 2.9 2.0": ["theraputic"], "9.5 8.8 13.5": ["nurdle"], "5.0 4.8 2.0": ["microsystem"], "20.8 6.6 14.0": ["poncy"], "5.6 10.2 21.6": ["brads"], "5.6 22.0 14.8": ["paintballers"], "10.1 10.4 12.4": ["expedients"], "-0.9 6.3 23.7": ["besan"], "15.0 -3.3 0.0": ["preloads"], "4.7 7.7 3.0": ["disrobes"], "2.0 4.2 9.2": ["unrenovated"], "-2.5 1.6 -0.5": ["reactivations"], "8.2 19.7 4.5": ["fastly"], "13.2 17.2 18.3": ["overpopulating"], "4.5 6.2 10.4": ["linocut"], "-1.9 14.6 8.0": ["economizer"], "7.5 3.7 11.8": ["downpipe"], "0.4 8.2 11.1": ["queeny"], "-0.1 9.9 10.9": ["knowledgably"], "7.0 1.1 4.2": ["photochemistry"], "2.3 17.3 6.9": ["irreconcilably"], "6.5 1.8 5.8": ["yoon"], "3.4 8.9 2.9": ["unstaged"], "-3.3 5.1 13.5": ["synovial"], "-0.2 1.3 5.1": ["salwars"], "6.8 0.7 8.5": ["walkaround"], "17.7 -1.0 7.5": ["precio"], "6.7 -1.1 9.5": ["produc"], "4.4 6.4 7.0": ["garbageman"], "-4.0 5.6 3.0": ["recommenders"], "2.7 9.6 13.4": ["brady"], "1.5 16.7 8.2": ["multicarrier"], "-6.1 3.1 1.1": ["alderpersons"], "6.3 5.2 14.5": ["rey"], "17.6 10.9 25.4": ["demitasse"], "2.1 5.1 10.7": ["beatifications"], "-4.2 8.9 18.6": ["blancs"], "10.3 3.1 21.5": ["paddlewheeler"], "8.4 15.6 4.4": ["shatteringly"], "2.5 5.2 15.1": ["gleanings"], "-2.1 4.1 8.1": ["optionees"], "11.0 7.3 14.9": ["blankies"], "2.0 12.3 12.5": ["stickability"], "1.1 5.8 5.7": ["oleh"], "6.5 9.6 -5.7": ["gapless"], "-6.0 -9.9 5.5": ["perinatologist"], "-1.4 14.4 12.0": ["decon"], "-2.2 9.5 8.8": ["biosurveillance"], "9.0 8.6 36.7": ["pimentos"], "-0.8 3.3 5.0": ["discrepency"], "-1.2 19.2 9.4": ["judgmentalism"], "-4.7 4.5 4.4": ["dobutamine"], "2.6 12.9 2.5": ["pacifies"], "11.3 20.2 4.5": ["centripetal"], "5.0 12.3 3.4": ["intensifier"], "18.3 10.4 23.7": ["globule"], "14.1 9.0 11.0": ["buzzin"], "-5.5 22.3 5.0": ["accomplishable"], "11.5 22.6 11.7": ["narcs"], "6.2 8.2 8.9": ["harddisk"], "10.2 1.6 12.9": ["catwalkers"], "12.7 0.4 12.0": ["repositionable"], "13.0 2.6 16.7": ["douglas"], "6.6 8.4 9.5": ["yobbish"], "2.1 8.4 16.4": ["tameness"], "13.1 -5.2 7.4": ["lightboxes"], "6.4 12.0 15.4": ["middled"], "7.1 14.0 8.3": ["crescendoing"], "7.3 9.7 15.6": ["couth"], "7.0 8.4 12.9": ["vacuole"], "2.5 12.1 4.6": ["photodynamic"], "4.1 5.4 7.4": ["simular"], "-0.6 8.6 7.0": ["vorinostat"], "-1.1 17.8 6.8": ["citzens"], "10.3 10.3 13.6": ["dreamtime"], "11.9 6.7 14.9": ["holer"], "13.7 10.4 8.2": ["bearpit"], "1.1 -1.8 9.1": ["congatec"], "13.2 5.7 -3.4": ["probings"], "6.0 11.1 8.0": ["nocturnes"], "6.6 0.5 18.8": ["brent"], "16.2 15.4 33.0": ["nuthatch"], "-6.6 10.6 2.3": ["conservatee"], "2.6 11.4 3.6": ["countercharge"], "0.5 -1.3 -0.2": ["progammes"], "0.6 10.8 15.6": ["spinosad"], "5.8 -9.5 5.0": ["lle"], "5.3 3.3 39.1": ["puttanesca"], "5.2 -2.5 7.6": ["aday"], "-3.6 4.5 0.2": ["playlisted"], "9.6 -0.8 2.9": ["bebo"], "12.9 16.5 13.4": ["pillock"], "7.5 2.1 25.1": ["lengua"], "13.8 3.6 14.0": ["fuji"], "6.6 2.7 14.0": ["trashiness"], "11.7 13.3 15.0": ["wowser"], "5.5 13.8 10.7": ["halloysite"], "3.1 14.0 10.9": ["caginess"], "5.2 3.2 16.4": ["twizzles"], "4.5 6.1 5.5": ["repowered"], "5.5 5.6 27.2": ["pomodoro"], "8.4 5.0 10.0": ["snappiest"], "4.9 10.5 9.3": ["cherrypick"], "3.8 6.0 19.4": ["zardozi"], "17.0 13.3 17.9": ["stetson"], "-0.9 7.2 -1.1": ["intracardiac"], "6.4 -0.5 8.1": ["harvard"], "7.1 0.1 6.4": ["demountables"], "-1.0 2.7 -1.2": ["aprepitant"], "6.4 5.9 -1.3": ["sexts"], "-0.1 17.9 8.0": ["cosine"], "8.4 4.9 9.8": ["drei"], "17.8 22.3 13.9": ["vulpine"], "-4.6 11.1 9.3": ["househelp"], "8.6 3.3 9.0": ["lamplighter"], "2.5 2.6 3.0": ["refurnishing"], "2.9 15.5 2.4": ["universalizing"], "6.7 17.8 4.0": ["coteries"], "6.6 -0.4 -3.0": ["unsalaried"], "1.1 -3.0 -1.6": ["univeristy"], "3.2 3.4 -1.8": ["nineth"], "3.1 17.3 9.6": ["pretention"], "12.6 3.4 6.4": ["dimunitive"], "1.8 5.5 16.9": ["kundan"], "-0.5 11.1 47.7": ["longlining"], "12.8 29.2 25.2": ["jarhead"], "5.6 9.5 9.3": ["competely"], "15.9 18.3 11.4": ["bearcat"], "6.2 12.5 14.3": ["hydrometer"], "11.6 7.3 4.6": ["microtonal"], "3.3 4.0 8.0": ["metamorphism"], "21.3 2.6 31.2": ["waterlilies"], "-2.9 20.9 13.3": ["sadnesses"], "-3.6 6.5 -5.7": ["chaplaincies"], "-1.1 5.7 8.7": ["geostatistical"], "18.3 9.8 5.8": ["unhitch"], "11.2 7.4 7.6": ["ometer"], "8.9 -0.0 8.4": ["idaho"], "8.3 13.5 20.2": ["blowy"], "14.2 8.9 13.5": ["superliner"], "-3.4 5.5 15.1": ["punjabi"], "5.9 9.3 7.7": ["bootlid"], "-2.6 25.0 7.8": ["verbalise"], "5.2 14.3 33.6": ["hellbenders"], "8.4 8.8 17.1": ["roundelay"], "8.7 18.3 7.2": ["integrationists"], "-7.5 -5.1 5.1": ["mmscf"], "16.0 2.6 22.4": ["wellingtons"], "8.4 -0.3 0.8": ["bootmaker"], "7.0 12.9 33.9": ["zander"], "12.8 14.0 27.4": ["wolfed"], "-11.6 10.0 3.8": ["chronicity"], "1.9 14.4 -1.4": ["effectives"], "12.8 11.0 4.1": ["competetion"], "-1.7 11.4 2.0": ["becloud"], "8.6 1.8 -2.9": ["commuity"], "9.3 13.0 20.0": ["kitesurfers"], "15.9 4.5 18.7": ["braincase"], "7.4 6.3 5.7": ["dak"], "16.0 2.3 30.2": ["kringle"], "-1.9 13.2 -5.0": ["detenus"], "11.1 15.9 18.5": ["rimshot"], "-4.5 1.3 9.6": ["osteomalacia"], "6.8 20.1 7.0": ["kaffirs"], "-2.5 4.7 7.2": ["fingerstick"], "-2.4 9.0 12.4": ["bursty"], "-0.0 -5.2 -2.3": ["repayed"], "-1.3 18.5 6.6": ["antinarcotics"], "17.8 6.1 9.5": ["caja"], "9.3 18.9 16.9": ["moonstruck"], "11.0 14.0 11.5": ["kh"], "5.7 -1.5 6.7": ["phd"], "-0.8 5.3 12.5": ["hypertensives"], "19.4 6.8 8.1": ["delapidated"], "6.4 8.9 7.4": ["indexable"], "12.4 11.8 2.1": ["overexuberant"], "8.1 9.1 11.4": ["tropopause"], "8.2 -3.6 15.5": ["punto"], "13.4 18.9 6.8": ["uncross"], "15.1 7.4 -2.9": ["immortalising"], "7.9 -5.0 8.9": ["biotechnologist"], "3.5 4.6 11.5": ["bioflavonoids"], "7.8 13.4 1.6": ["exorcized"], "8.1 30.0 7.2": ["marxists"], "6.0 3.2 12.2": ["caroused"], "3.5 15.2 0.5": ["believeable"], "-4.8 3.4 4.6": ["presurgical"], "-1.2 0.5 7.8": ["roundtrippers"], "2.4 17.0 10.9": ["winnin"], "5.7 26.0 8.9": ["isi"], "0.1 1.2 14.1": ["ninths"], "-5.6 3.7 15.3": ["thrifting"], "18.6 16.3 26.7": ["avians"], "-5.8 -2.5 1.2": ["ezogabine"], "15.1 10.5 17.1": ["downturned"], "4.4 9.1 12.3": ["notarios"], "14.7 6.3 -0.1": ["moblog"], "8.8 0.1 7.3": ["zer"], "13.9 -10.7 11.0": ["quinceaneras"], "15.4 20.7 16.6": ["parasitically"], "6.1 15.9 8.6": ["birdstrike"], "6.8 13.6 9.0": ["scramjets"], "1.3 9.3 15.1": ["stepsiblings"], "10.9 5.7 40.9": ["mignonette"], "7.5 11.7 5.8": ["keycards"], "22.9 5.2 18.9": ["flitter"], "1.6 13.0 7.6": ["indefensibly"], "2.2 2.2 -0.4": ["rechecks"], "4.5 16.5 11.4": ["fff"], "7.8 -1.1 9.6": ["devaswom"], "11.7 5.0 19.1": ["stonecutters"], "3.3 8.5 6.9": ["postscripts"], "0.5 9.8 1.4": ["matrixed"], "2.8 23.8 10.3": ["sarge"], "5.0 -0.3 3.5": ["biodiesels"], "8.9 29.3 7.3": ["bloodlessly"], "6.0 8.0 22.7": ["iness"], "-15.6 -1.6 3.2": ["reincarcerated"], "-2.0 8.2 18.5": ["coinages"], "11.3 22.0 25.2": ["reacher"], "14.5 10.2 35.1": ["coracle"], "9.4 13.2 4.2": ["paly"], "5.4 25.4 -0.7": ["atack"], "6.2 18.9 10.9": ["softkeys"], "2.0 15.9 -2.1": ["orientating"], "7.3 4.7 27.6": ["boysenberries"], "19.2 14.0 10.8": ["parvenu"], "2.0 2.0 8.2": ["arco"], "15.7 -3.4 -7.8": ["digitalise"], "7.4 11.1 10.7": ["specular"], "-11.7 4.7 -0.7": ["pedagogically"], "3.0 6.1 7.2": ["downtrading"], "16.4 15.0 19.8": ["turnin"], "6.6 16.8 15.8": ["beriberi"], "-3.2 11.1 8.1": ["respirations"], "-0.3 -1.2 14.8": ["shih"], "3.2 10.4 19.7": ["embarkations"], "-2.6 11.5 2.9": ["resposible"], "11.8 6.1 7.2": ["gma"], "7.9 7.3 39.3": ["waterbird"], "14.5 3.6 3.5": ["mimeograph"], "-3.7 15.1 6.2": ["internments"], "17.3 0.7 16.8": ["offthe"], "-3.0 14.7 5.7": ["ciphering"], "-5.9 2.4 4.9": ["churchs"], "-7.1 5.4 4.9": ["stls"], "5.6 8.3 10.1": ["soapland"], "12.0 29.6 9.8": ["allegorically"], "3.7 14.8 10.5": ["psy"], "1.9 16.9 15.4": ["dearness"], "-0.8 9.3 6.8": ["straightline"], "5.5 18.7 9.6": ["erosional"], "1.8 17.8 8.0": ["deism"], "-5.2 5.7 2.9": ["slideoffs"], "2.1 -0.9 7.4": ["eprocurement"], "9.5 6.4 11.5": ["perfuming"], "-0.4 2.2 5.0": ["dualization"], "7.2 17.7 17.4": ["sistas"], "5.8 9.9 5.4": ["hopscotches"], "9.5 14.1 11.5": ["gamecube"], "5.2 7.6 13.8": ["mustiness"], "12.5 -1.7 7.1": ["nacional"], "11.3 14.4 22.3": ["sponger"], "4.6 8.1 4.4": ["neuroma"], "12.7 13.8 14.7": ["hoick"], "2.2 13.3 9.7": ["psephologists"], "15.9 12.8 3.9": ["governmen"], "17.8 8.7 28.0": ["capercaillie"], "9.1 25.2 12.5": ["savageness"], "-0.5 12.7 8.5": ["vitalizing"], "9.1 12.3 11.8": ["bevels"], "16.3 24.1 22.0": ["nevermore"], "-1.3 3.9 2.0": ["reimported"], "1.3 7.4 23.0": ["artemisia"], "-5.5 0.9 5.3": ["overtesting"], "5.5 15.0 22.4": ["knucklers"], "9.2 5.6 12.5": ["masse"], "6.9 3.7 7.1": ["perfluorochemicals"], "2.6 2.8 12.5": ["helen"], "16.5 3.6 5.2": ["webtop"], "0.3 8.9 9.1": ["valgus"], "9.3 17.9 12.7": ["groundlings"], "-4.0 -1.8 12.1": ["osteo"], "6.6 7.7 17.4": ["scrunchie"], "10.2 9.2 8.1": ["goodlooking"], "4.4 1.1 7.1": ["adex"], "10.3 6.9 16.2": ["stelae"], "7.6 9.0 11.6": ["haf"], "-4.0 11.8 9.5": ["vinyasa"], "21.7 9.4 27.1": ["cornucopias"], "-9.7 17.9 4.2": ["nonfictional"], "0.7 26.3 12.5": ["hardass"], "9.6 15.8 3.0": ["siccing"], "7.9 18.3 11.2": ["gamertags"], "10.5 10.5 12.8": ["sheilas"], "-1.1 9.9 3.9": ["penatly"], "14.4 11.1 24.0": ["ultramarine"], "-2.2 8.5 6.1": ["toxemia"], "11.4 -7.9 16.1": ["rfp"], "7.6 5.9 1.7": ["unvalidated"], "7.0 10.6 13.4": ["creampuffs"], "-3.2 3.5 -8.8": ["registerd"], "9.5 40.2 9.6": ["weaponless"], "10.8 15.4 31.1": ["bayberry"], "3.7 4.0 10.3": ["celebrative"], "3.4 41.4 9.6": ["civillians"], "0.7 -5.0 11.6": ["yng"], "10.1 23.3 13.3": ["klan"], "12.9 14.9 9.2": ["mudbrick"], "7.2 1.7 23.3": ["rosemaling"], "8.7 11.4 14.1": ["wintersports"], "2.3 11.2 6.9": ["photosensitizer"], "9.0 2.1 5.0": ["tj"], "9.2 9.7 35.0": ["livewells"], "12.8 9.1 -0.3": ["newboy"], "-0.4 3.3 19.1": ["coumarin"], "-6.2 9.9 21.4": ["freshet"], "2.0 25.7 12.1": ["horribleness"], "-2.5 4.2 -1.4": ["confrence"], "-4.0 15.2 5.5": ["melanopsin"], "3.3 5.7 16.2": ["flossed"], "-1.4 3.3 9.4": ["gameweek"], "1.9 2.3 13.4": ["ock"], "17.9 9.2 8.3": ["funkadelic"], "-15.1 19.5 7.5": ["deescalate"], "-2.5 3.1 12.6": ["nonwinners"], "-1.1 9.9 4.5": ["seemd"], "-7.8 14.8 5.2": ["ganetespib"], "-4.3 11.6 6.0": ["strom"], "9.5 10.7 10.2": ["supramolecular"], "9.0 8.7 17.5": ["euthanase"], "-5.4 -6.5 -4.2": ["mahr"], "12.4 6.1 4.5": ["soundboards"], "2.7 12.6 25.0": ["diapause"], "2.2 11.0 1.7": ["elate"], "4.3 3.5 14.6": ["twinged"], "12.4 10.6 3.6": ["electrohydraulic"], "3.4 13.3 14.5": ["beaux"], "9.2 9.1 17.0": ["replants"], "-2.1 8.9 7.4": ["acharya"], "4.9 10.0 5.9": ["gens"], "9.1 12.2 11.6": ["flowstation"], "7.3 30.6 1.9": ["boobytrapped"], "4.2 -0.8 20.7": ["fis"], "5.3 6.7 8.5": ["contiguously"], "8.3 12.8 8.4": ["coverboy"], "0.0 10.7 -7.2": ["publicy"], "11.8 19.6 20.8": ["gutbuster"], "0.6 11.3 6.1": ["malaysian"], "2.3 -0.6 4.7": ["ltr"], "3.4 0.1 9.8": ["steelbands"], "5.8 10.5 7.2": ["amort"], "-1.2 6.5 9.5": ["downregulated"], "22.1 -3.4 9.4": ["dustry"], "8.4 -4.2 32.6": ["gras"], "4.4 6.2 8.7": ["rewardingly"], "-2.6 5.6 8.3": ["kritis"], "11.4 14.8 4.2": ["woodenly"], "8.7 27.0 4.8": ["rheostat"], "13.6 20.0 13.7": ["penlight"], "0.0 24.0 23.5": ["beneficials"], "3.5 10.2 21.9": ["trapline"], "10.1 19.7 18.5": ["turtled"], "1.1 0.7 11.5": ["horas"], "9.2 10.3 14.0": ["dolor"], "4.5 7.7 2.5": ["shek"], "-10.3 4.1 15.0": ["pended"], "-7.6 13.8 -3.8": ["unrebutted"], "11.2 9.5 2.1": ["steelier"], "4.9 11.4 9.0": ["diane"], "8.7 3.5 3.7": ["sungura"], "6.0 10.3 11.4": ["endosome"], "20.6 7.5 17.0": ["saltire"], "12.7 1.5 22.3": ["carnaval"], "12.1 9.0 10.6": ["claycourts"], "6.3 11.1 11.9": ["contactmusic"], "8.4 19.5 15.4": ["territorialism"], "8.7 10.2 13.9": ["diffidently"], "10.3 2.4 -2.5": ["ibibo"], "1.4 21.4 1.5": ["courageousness"], "10.5 12.2 23.6": ["boatie"], "11.0 9.1 9.6": ["infilled"], "10.1 13.1 7.0": ["spoonfed"], "-1.3 3.8 9.4": ["pentatonic"], "6.9 4.3 14.9": ["chukkas"], "15.2 6.8 26.8": ["mosasaur"], "5.7 16.7 10.2": ["snowslides"], "5.5 6.7 6.6": ["welfarist"], "-10.9 1.3 -1.9": ["valuably"], "-0.2 -1.8 7.4": ["pra"], "14.4 2.7 14.4": ["dudettes"], "-4.2 -4.8 1.1": ["bursars"], "-0.7 21.5 3.5": ["qisas"], "2.0 6.7 14.1": ["bari"], "12.3 3.1 6.0": ["babyboomers"], "17.7 6.8 12.4": ["faceful"], "22.0 13.0 16.2": ["befouling"], "5.0 22.2 11.2": ["joes"], "-8.5 25.4 2.3": ["introspectively"], "12.4 0.5 7.1": ["clo"], "14.5 13.6 14.7": ["grandpappy"], "-4.2 -4.2 8.1": ["alchol"], "0.6 16.4 11.3": ["forewarns"], "7.9 0.0 20.3": ["koha"], "2.2 14.9 11.9": ["superuser"], "-2.5 1.0 10.3": ["wp"], "0.3 -7.5 8.4": ["sesssion"], "3.2 0.6 3.0": ["editon"], "-0.9 4.4 7.3": ["sightholder"], "-0.6 13.7 26.9": ["dipnetting"], "-2.5 9.1 10.7": ["varus"], "20.4 10.8 14.5": ["lotharios"], "23.5 2.5 11.7": ["lollypops"], "15.5 9.0 2.3": ["ecoterrorists"], "6.8 11.5 5.9": ["beautifull"], "5.3 3.0 -1.1": ["onl"], "2.6 1.8 3.3": ["gj"], "6.2 9.9 11.4": ["impractically"], "-3.9 13.7 4.5": ["codebook"], "15.1 4.8 27.0": ["rimu"], "13.6 8.1 24.9": ["snickerdoodles"], "13.3 18.7 2.4": ["groundlessly"], "26.1 6.9 18.8": ["plushy"], "8.7 6.8 22.3": ["tampa"], "26.3 20.2 10.6": ["toybox"], "9.8 25.9 12.0": ["depravities"], "23.5 28.4 16.7": ["monsterous"], "2.5 8.0 9.2": ["sehr"], "10.0 3.9 39.3": ["sauted"], "3.2 10.0 1.2": ["prosecuters"], "11.8 11.9 10.5": ["silkily"], "8.2 19.1 7.6": ["ratbags"], "2.5 4.9 8.3": ["cannabidiol"], "-9.0 2.9 2.7": ["thyroidectomy"], "-0.2 17.3 -3.6": ["unequivocably"], "6.9 4.7 36.6": ["bowheads"], "-2.2 6.4 1.1": ["maint"], "6.9 9.8 1.3": ["resonantly"], "5.6 9.5 -3.5": ["enquirer"], "6.4 7.7 8.2": ["ferguson"], "6.1 22.9 15.5": ["sectionalism"], "1.1 17.7 8.3": ["pairwise"], "12.3 13.1 22.7": ["skunky"], "13.9 11.3 23.1": ["ricer"], "26.0 8.3 15.3": ["bedsprings"], "11.7 17.3 10.3": ["insensitivities"], "-7.2 1.9 5.0": ["akim"], "11.7 24.5 25.7": ["cholla"], "7.5 13.0 15.6": ["faketeams"], "10.3 14.9 -1.4": ["communicational"], "-6.2 21.4 4.8": ["reproved"], "-5.3 9.6 13.4": ["calcaneus"], "9.2 4.1 4.7": ["flyscreen"], "2.4 7.8 12.1": ["hypocretin"], "11.3 8.2 32.1": ["caladium"], "6.3 8.2 4.8": ["uncontrived"], "-2.8 13.0 7.8": ["sulfa"], "-2.9 0.1 13.1": ["oligos"], "5.8 11.0 16.7": ["mansionization"], "-4.5 -0.0 4.2": ["tibolone"], "19.9 3.6 15.2": ["rubberband"], "20.8 8.3 12.8": ["insatiably"], "11.3 10.6 3.0": ["nanotechnological"], "1.8 14.3 9.2": ["mandatories"], "13.9 6.5 25.1": ["noodlers"], "11.1 5.5 15.6": ["poos"], "4.9 20.3 7.9": ["yout"], "1.2 5.0 14.7": ["rhia"], "-0.9 2.3 8.9": ["amature"], "-0.5 2.7 9.2": ["merchantable"], "3.8 25.7 7.3": ["inconstancy"], "-12.7 10.3 7.9": ["epidemiologically"], "5.4 11.7 12.8": ["amiga"], "11.0 3.7 -7.0": ["rehaul"], "10.4 14.0 11.9": ["smartypants"], "4.4 11.7 13.2": ["succesive"], "1.9 11.3 -3.0": ["ministration"], "17.3 7.0 10.6": ["bubs"], "1.4 13.9 13.0": ["rowhome"], "3.0 14.2 10.5": ["paravirtualization"], "18.7 4.5 9.1": ["gaslights"], "18.5 10.0 14.6": ["whenthe"], "-0.6 14.8 6.9": ["cipro"], "-3.5 5.2 14.6": ["apeice"], "9.6 28.2 30.4": ["cankerworms"], "-1.4 5.7 5.5": ["mandays"], "11.1 14.2 17.7": ["vag"], "1.7 2.4 24.7": ["reelers"], "3.7 12.0 7.1": ["collimated"], "14.2 0.1 2.7": ["superleague"], "2.0 3.1 13.4": ["aves"], "12.7 3.7 11.4": ["butthe"], "7.6 6.8 8.0": ["phillips"], "10.2 7.7 40.3": ["sunchokes"], "-3.6 10.3 12.8": ["nako"], "9.8 17.5 15.7": ["polymorph"], "3.7 4.3 13.2": ["taekwando"], "2.1 6.8 11.8": ["carpal"], "9.1 12.3 14.9": ["dholak"], "0.6 6.0 6.8": ["filmaker"], "14.2 0.3 12.9": ["tiptop"], "13.2 10.3 27.8": ["ranunculus"], "-2.2 0.7 12.9": ["humeral"], "8.9 15.2 16.0": ["gre"], "-7.9 2.8 13.8": ["watermaster"], "-1.6 23.1 5.2": ["heterodoxy"], "10.4 3.1 12.2": ["fengshui"], "-3.3 20.2 5.2": ["prejudgments"], "16.8 18.7 10.0": ["cide"], "8.1 10.4 12.9": ["stip"], "-4.5 -4.1 -2.4": ["orals"], "11.8 1.7 6.1": ["acoustician"], "7.3 6.0 4.2": ["underdelivered"], "7.9 9.2 5.5": ["camerapersons"], "-6.1 5.4 -2.1": ["abidance"], "-3.5 -2.8 12.6": ["fourplexes"], "6.6 -1.5 27.1": ["pelleted"], "8.2 1.6 19.0": ["workboots"], "6.3 5.3 15.4": ["pulver"], "5.7 11.1 43.4": ["eulachon"], "-4.3 5.6 4.6": ["empyema"], "-0.2 5.4 14.9": ["shechita"], "0.6 5.7 3.5": ["backstraight"], "9.5 4.4 12.7": ["matchball"], "3.3 7.5 3.3": ["universalise"], "-2.0 15.1 2.4": ["structuralist"], "3.2 -1.6 17.4": ["daan"], "15.3 9.4 7.4": ["unfelt"], "-10.9 -0.0 4.0": ["directress"], "-1.1 5.4 15.3": ["inoculant"], "8.9 3.9 10.8": ["harks"], "-5.4 1.9 1.2": ["dicussion"], "8.7 27.4 11.3": ["chickenshit"], "8.6 12.5 12.6": ["shakeouts"], "-5.7 9.4 5.1": ["psychiatrically"], "11.8 14.9 4.3": ["manship"], "8.4 12.7 13.4": ["loansharks"], "17.8 11.2 30.5": ["crullers"], "3.0 11.5 17.0": ["abscessed"], "-3.0 10.7 -1.2": ["inceptions"], "10.4 15.8 9.8": ["backrub"], "11.0 3.5 14.2": ["funkified"], "4.1 7.8 3.3": ["forcings"], "24.6 10.8 22.2": ["flappy"], "3.7 -0.8 5.7": ["ric"], "14.4 10.2 24.5": ["gyres"], "0.1 13.5 12.8": ["banya"], "8.8 -1.1 11.2": ["watchband"], "0.6 -3.5 3.3": ["vibey"], "13.9 2.3 38.0": ["fulmars"], "-7.4 2.1 -2.9": ["restitute"], "14.5 9.0 14.0": ["katakana"], "15.8 4.6 11.5": ["hausfrau"], "12.4 29.4 19.1": ["duelists"], "3.5 9.3 11.7": ["unpretentiousness"], "-6.2 5.4 4.3": ["esophagectomy"], "3.8 2.6 1.8": ["fof"], "0.6 0.3 12.6": ["handson"], "9.5 3.5 18.0": ["busbar"], "8.4 3.9 20.0": ["pitmaster"], "10.3 12.4 30.4": ["californica"], "-8.0 12.8 3.2": ["jobholder"], "2.0 2.0 20.4": ["steeplechases"], "7.6 15.2 6.7": ["overuses"], "6.0 -3.2 3.0": ["bookplates"], "12.3 10.2 6.4": ["sleezy"], "2.6 4.8 19.0": ["mers"], "2.9 -3.2 8.9": ["gn"], "-3.5 5.5 7.5": ["strikouts"], "14.3 7.8 10.1": ["momentousness"], "-5.1 17.4 3.7": ["cooptation"], "11.0 25.4 8.2": ["fanboyism"], "9.1 14.8 16.9": ["oakland"], "5.8 6.7 31.2": ["headcheese"], "6.6 9.8 6.0": ["countrymate"], "-8.3 4.5 1.7": ["pastorates"], "2.5 11.6 1.1": ["extravasation"], "11.2 12.3 21.6": ["pish"], "4.0 7.4 2.9": ["peo"], "1.6 19.5 1.8": ["ablating"], "-5.2 4.4 10.0": ["intercostal"], "5.8 4.8 5.8": ["mh"], "3.6 13.4 -2.2": ["outdriven"], "8.9 11.5 20.8": ["downland"], "7.4 13.0 -2.5": ["defibrillate"], "10.0 1.5 16.5": ["landau"], "6.1 22.6 20.3": ["trapos"], "1.9 14.3 12.2": ["dosti"], "-4.9 16.7 -2.4": ["prophethood"], "8.2 6.0 20.5": ["moneylending"], "5.1 9.5 10.6": ["certaintly"], "8.2 13.5 44.2": ["overharvested"], "-0.5 18.2 11.7": ["moralise"], "1.8 4.4 -1.3": ["sensationalizes"], "8.9 5.1 13.4": ["enterprisers"], "1.6 4.2 14.6": ["kurti"], "16.9 20.4 6.2": ["shamefacedly"], "6.8 9.8 5.0": ["spel"], "2.7 4.7 11.3": ["entender"], "11.3 20.1 10.3": ["snarks"], "11.8 8.0 12.5": ["letterforms"], "12.3 15.7 25.3": ["owlet"], "-1.8 8.7 4.1": ["cholecalciferol"], "-4.4 11.9 3.9": ["xxvi"], "-5.9 8.9 17.3": ["heterosis"], "-3.8 -1.6 12.5": ["organochlorines"], "17.3 -1.9 -16.7": ["agrement"], "9.2 19.8 14.7": ["oedipal"], "23.0 10.0 25.1": ["barbies"], "9.1 11.6 5.8": ["befittingly"], "-2.8 32.5 3.1": ["emplacing"], "8.3 6.2 21.3": ["myxomatosis"], "0.7 10.7 2.1": ["blurbed"], "3.7 16.4 12.8": ["kraals"], "3.8 12.2 12.1": ["housesitter"], "-5.0 15.5 9.0": ["pir"], "19.0 15.3 16.5": ["acropolis"], "3.7 11.8 11.2": ["biogenesis"], "3.6 13.3 2.6": ["postcommunist"], "2.6 6.5 12.2": ["leisured"], "3.4 -3.8 9.3": ["phentolamine"], "8.0 8.1 2.2": ["avantgarde"], "8.4 23.0 19.4": ["gerund"], "11.1 2.6 13.3": ["boppin"], "3.0 6.3 11.3": ["oversupplying"], "-2.4 7.9 12.8": ["kuia"], "-1.0 1.7 4.7": ["relooking"], "11.1 15.9 6.0": ["slovenliness"], "6.4 17.9 3.9": ["hatefest"], "4.5 7.9 1.7": ["performant"], "8.1 28.5 4.7": ["meekest"], "7.5 -2.1 13.3": ["shoping"], "6.9 6.9 9.8": ["fundus"], "5.9 8.9 4.6": ["microdrive"], "5.3 20.6 10.9": ["tiltrotor"], "7.0 1.5 7.6": ["isocyanates"], "2.4 3.6 14.3": ["hsin"], "-2.1 13.6 5.0": ["statured"], "13.2 18.9 12.0": ["wowsers"], "10.5 -0.1 12.5": ["derma"], "12.1 8.0 11.7": ["liquify"], "-2.3 14.2 14.8": ["terroirs"], "7.4 1.4 -0.2": ["namecheck"], "23.1 8.1 23.5": ["dromedary"], "6.6 -2.5 0.3": ["dena"], "9.2 17.3 8.1": ["aether"], "4.3 11.3 -0.1": ["jiggered"], "-3.2 -1.1 1.6": ["requalified"], "6.1 9.5 10.1": ["aquaintance"], "8.5 9.4 13.0": ["rabbiting"], "9.9 6.2 31.3": ["jalebis"], "8.7 11.8 7.2": ["panchromatic"], "2.4 9.6 6.2": ["cellsites"], "1.1 10.1 12.7": ["apne"], "16.7 4.8 18.8": ["tarpaper"], "-4.5 6.0 3.3": ["sarpanchs"], "9.3 -1.4 13.9": ["teether"], "-0.2 6.4 6.4": ["ptosis"], "8.9 6.1 5.6": ["wisemen"], "0.3 8.4 9.0": ["fews"], "2.9 8.4 3.0": ["furture"], "14.6 11.6 14.9": ["ziplining"], "-2.8 4.2 2.7": ["paraplanner"], "11.5 5.8 7.5": ["arg"], "-4.6 4.0 10.9": ["upstaters"], "-3.2 5.0 9.8": ["easings"], "17.8 3.1 7.1": ["overinvested"], "17.2 10.3 16.3": ["penknives"], "-2.3 10.5 1.7": ["diatonic"], "12.2 -2.7 2.8": ["customises"], "9.5 8.4 9.9": ["hectically"], "2.2 13.1 8.6": ["undershoots"], "1.5 14.1 11.9": ["pokecheck"], "12.4 8.5 21.3": ["gentian"], "5.6 22.1 15.7": ["cheapshot"], "4.1 10.9 8.7": ["reopposes"], "12.7 15.2 8.5": ["clunkily"], "0.1 12.4 3.1": ["outshout"], "1.4 -3.5 2.6": ["ecobee"], "3.7 10.6 6.7": ["tranquiliser"], "-14.1 7.1 5.0": ["lymphadenectomy"], "0.4 -8.1 13.9": ["giclees"], "15.3 2.0 14.2": ["trenchers"], "13.3 17.8 25.2": ["weeder"], "1.1 1.9 6.0": ["stepdown"], "9.2 5.6 28.4": ["khao"], "0.5 1.8 -0.8": ["enherent"], "-1.4 4.1 9.7": ["inguinal"], "5.9 7.5 12.8": ["gul"], "-3.2 10.5 7.6": ["tigecycline"], "13.2 3.9 9.9": ["portugal"], "10.6 3.5 24.7": ["breakfront"], "20.4 6.9 31.2": ["coney"], "-4.3 6.2 12.8": ["histopathologic"], "10.7 10.2 2.7": ["desribed"], "11.9 10.3 15.6": ["underbite"], "6.8 24.1 4.0": ["conspiracist"], "-6.7 -3.6 -0.9": ["tirofiban"], "16.6 13.1 21.4": ["addling"], "13.4 6.8 10.7": ["bagatelle"], "2.1 5.8 6.8": ["houseman"], "-4.6 13.5 8.9": ["doshas"], "12.8 7.2 23.2": ["papillae"], "0.7 8.4 0.5": ["bodystyle"], "14.1 5.9 4.8": ["hebben"], "8.1 32.7 -1.0": ["archfoe"], "7.5 9.8 12.7": ["saloonkeeper"], "-1.7 25.3 -1.3": ["loyality"], "-2.6 25.2 5.5": ["asperity"], "21.0 15.8 17.4": ["moonbeam"], "10.4 11.1 10.6": ["masterstrokes"], "-8.7 3.2 0.9": ["thromboprophylaxis"], "5.0 27.1 8.5": ["federals"], "8.1 1.7 3.0": ["orthobiologic"], "10.9 8.0 21.9": ["cathouse"], "2.1 15.8 36.2": ["stonefly"], "2.2 5.5 5.4": ["allison"], "11.7 19.1 3.5": ["gameboy"], "-6.5 13.1 16.1": ["rurals"], "-5.0 11.0 7.1": ["usp"], "3.9 -0.6 10.1": ["aise"], "12.4 4.8 13.0": ["fcast"], "-4.0 14.7 10.7": ["glycosides"], "6.4 6.8 8.9": ["nanoporous"], "4.7 -4.9 7.2": ["citybizlist"], "20.9 15.3 12.0": ["malarky"], "-2.4 4.7 2.3": ["commissionership"], "-6.2 2.8 6.9": ["ureteral"], "3.0 8.9 -3.7": ["notability"], "-13.1 5.6 1.5": ["communtiy"], "1.5 9.6 3.8": ["housefire"], "16.3 7.3 15.6": ["poncey"], "8.2 14.3 7.0": ["leakiness"], "9.9 12.2 13.5": ["impactors"], "-2.2 -1.5 2.4": ["aromatherapist"], "4.7 19.6 31.1": ["bobwhites"], "-0.2 5.5 18.7": ["cleanouts"], "8.5 13.8 25.2": ["cruciferous"], "2.8 8.3 26.6": ["toplessness"], "1.4 10.7 3.6": ["motocrosser"], "5.0 0.7 13.1": ["boroughwide"], "2.8 13.2 21.8": ["jess"], "6.4 11.2 3.6": ["wisened"], "14.2 4.2 6.9": ["dashiki"], "1.9 1.5 9.2": ["recision"], "-2.0 0.1 1.1": ["pacings"], "6.7 6.8 21.0": ["faro"], "13.7 10.0 29.9": ["coquina"], "14.6 8.1 37.0": ["yaki"], "5.1 0.9 16.7": ["sawmillers"], "1.9 12.9 13.3": ["loess"], "10.5 12.2 20.8": ["timey"], "-6.1 3.3 6.6": ["intersessional"], "9.8 9.1 17.2": ["placket"], "9.0 13.2 12.0": ["looniness"], "3.0 -5.6 9.2": ["tid"], "-0.2 3.1 9.5": ["hn"], "0.0 15.6 12.6": ["biomechanically"], "0.3 2.7 13.2": ["readopt"], "0.6 -0.3 0.4": ["telecentre"], "-6.4 1.8 7.0": ["phoner"], "17.4 16.6 9.9": ["machinelike"], "14.2 2.0 5.4": ["resi"], "-3.1 5.6 8.1": ["avobenzone"], "7.9 0.1 11.5": ["plena"], "12.4 1.0 8.6": ["nutriceutical"], "9.3 -0.8 6.9": ["nightclubbers"], "12.1 18.8 1.6": ["sattelite"], "7.1 7.1 10.0": ["dismantlers"], "11.7 9.9 17.6": ["frontons"], "-3.3 8.4 8.5": ["shortcutting"], "-0.6 -0.2 6.4": ["bimatoprost"], "4.3 3.4 6.1": ["unmusical"], "16.3 14.7 39.0": ["stinkbaits"], "8.3 4.9 4.7": ["geen"], "-10.7 8.1 4.9": ["expunction"], "-0.4 4.6 1.4": ["bibliographer"], "6.6 9.2 31.0": ["puckery"], "25.2 12.8 18.5": ["razorback"], "-2.1 1.9 8.8": ["leasee"], "5.5 18.2 11.2": ["overhitting"], "10.9 5.3 16.4": ["clastic"], "15.3 19.4 20.1": ["holo"], "3.6 8.6 10.2": ["paleoclimatologist"], "11.0 13.3 6.3": ["turnabouts"], "8.3 35.0 14.3": ["heliborne"], "-4.8 5.2 5.5": ["outturns"], "6.3 19.5 8.7": ["shotless"], "3.8 -0.3 10.9": ["tues"], "6.0 7.9 20.2": ["pubis"], "11.8 3.8 1.3": ["typewriting"], "2.9 5.4 9.4": ["winnner"], "0.2 11.6 10.3": ["bolton"], "8.8 21.4 15.7": ["goatherds"], "18.8 13.2 27.1": ["sharkskin"], "7.4 15.6 2.9": ["nomadism"], "7.6 26.0 -0.3": ["unholster"], "3.4 0.3 5.5": ["roadmapping"], "1.0 10.8 14.5": ["pterygium"], "19.9 6.1 13.0": ["untwist"], "-8.5 7.1 8.7": ["ecclesiological"], "7.2 32.1 -3.4": ["reconnaisance"], "2.2 12.0 1.1": ["embolisms"], "3.4 -2.0 9.3": ["keh"], "2.1 7.4 12.9": ["blebs"], "6.3 2.6 8.7": ["walter"], "6.5 -1.2 8.3": ["maintenace"], "-4.3 18.1 0.7": ["fuzes"], "-1.6 4.0 8.4": ["forodesine"], "8.6 3.5 9.4": ["coul"], "17.3 16.5 8.6": ["cheesily"], "9.7 -3.6 -1.9": ["appr"], "-6.4 1.7 9.3": ["annuitized"], "-0.7 12.0 3.3": ["facto"], "18.6 4.9 8.2": ["reregulate"], "1.7 8.0 3.0": ["exclusivities"], "14.2 11.7 1.9": ["dustiest"], "8.6 23.0 -0.4": ["manouvre"], "5.7 13.7 4.5": ["lifeblogging"], "8.5 1.8 9.9": ["flautists"], "7.5 3.7 18.9": ["jamaica"], "2.0 4.3 5.4": ["eno"], "16.5 11.0 44.6": ["samphire"], "11.7 -0.4 4.6": ["oyj"], "8.4 3.7 9.4": ["metreleptin"], "15.4 11.9 25.1": ["bandicoots"], "-0.0 18.2 3.7": ["dogtags"], "4.6 19.8 9.2": ["bidden"], "2.7 7.3 4.3": ["lez"], "8.3 3.6 7.6": ["revitalises"], "-5.1 7.3 20.5": ["gamay"], "18.1 -4.1 6.2": ["impressario"], "6.2 6.7 -1.2": ["cyclotrons"], "3.9 1.5 18.0": ["juan"], "2.2 0.8 7.1": ["ampules"], "11.2 4.4 6.8": ["cental"], "0.8 4.5 10.4": ["karakia"], "-2.5 7.2 5.4": ["unconvicted"], "6.1 7.6 11.6": ["nye"], "4.6 13.6 26.9": ["longleaf"], "2.1 -0.0 13.4": ["oligofructose"], "3.1 27.8 8.0": ["nobleness"], "1.4 2.5 4.2": ["stablised"], "0.0 8.3 1.2": ["traumatology"], "6.4 9.2 6.5": ["ound"], "-6.0 18.1 -2.8": ["unforgotten"], "3.0 3.9 6.3": ["jms"], "5.9 9.7 19.8": ["unladen"], "-4.6 -0.7 6.2": ["tristate"], "3.5 2.2 12.1": ["resorbed"], "12.8 12.1 36.0": ["swallowtails"], "2.3 24.2 6.7": ["lebanese"], "6.2 8.3 4.5": ["savoir"], "6.7 8.5 2.0": ["biodefence"], "5.9 1.2 3.0": ["giv"], "0.6 1.9 7.9": ["resettles", "onlies"], "23.7 11.8 26.5": ["homophone"], "3.4 18.3 4.2": ["coutries"], "7.4 4.8 12.2": ["biocrude"], "0.8 5.6 5.8": ["epicardial"], "4.2 9.7 33.9": ["seines"], "3.4 6.2 13.5": ["bono"], "7.7 26.9 9.6": ["misguidance"], "-5.1 6.8 2.3": ["lercanidipine"], "13.8 7.3 10.5": ["attatched"], "-4.5 8.6 9.0": ["hemostat"], "0.6 10.0 6.2": ["tunefully"], "-6.6 14.6 1.1": ["apneas"], "6.9 7.4 6.9": ["schmoozes"], "-0.1 5.1 10.3": ["careerhigh"], "-4.1 8.8 12.6": ["interpolates"], "-0.8 4.6 1.6": ["doorknocked"], "3.3 4.0 8.8": ["microstructural"], "-0.9 14.9 -7.2": ["trustable"], "8.9 7.6 8.0": ["nanobacteria"], "7.2 3.1 19.4": ["goethite"], "1.8 -2.1 4.5": ["np"], "5.1 11.1 15.4": ["oxidise"], "5.7 10.7 2.3": ["manch"], "-0.4 11.4 11.7": ["placekicks"], "0.1 9.8 8.1": ["certains"], "-3.9 13.2 -1.2": ["recruitable"], "10.4 -0.0 8.8": ["olympiad"], "2.8 -0.2 11.9": ["stanols"], "-1.9 11.6 8.9": ["unchecking"], "7.8 16.3 9.4": ["bascially"], "6.1 15.5 4.6": ["whitelisted"], "-5.1 -1.6 1.2": ["regualr"], "-3.2 12.7 4.8": ["bailee"], "-3.2 11.1 0.3": ["rideability"], "8.4 -2.4 8.6": ["casi"], "0.6 14.6 7.5": ["heartrate"], "15.7 1.4 14.2": ["labware"], "3.6 -12.6 -5.1": ["copresident"], "4.3 11.5 6.1": ["skinniness"], "9.9 6.2 27.2": ["pongal"], "6.6 2.7 6.7": ["refractometer"], "16.7 15.1 5.1": ["bizzaro"], "5.7 12.1 4.0": ["tuneable"], "4.4 5.1 16.0": ["cruz"], "2.3 17.6 12.1": ["obtusely"], "8.5 7.1 12.2": ["nanoengineering"], "14.3 4.5 35.0": ["boilies"], "1.0 -2.9 6.4": ["recarpeting"], "9.3 10.9 13.1": ["subcrop"], "-0.4 12.7 -2.7": ["importable"], "0.2 12.6 6.1": ["businesswise"], "0.1 13.2 15.7": ["drys"], "10.1 20.0 13.0": ["crats"], "10.8 14.1 18.5": ["shitfaced"], "7.1 2.4 6.3": ["ahhhs"], "8.3 15.1 5.0": ["diffracted"], "10.2 3.5 49.8": ["snoek"], "6.3 9.1 24.1": ["putrefied"], "34.2 3.9 1.2": ["stateowned"], "5.3 7.7 17.3": ["dzong"], "9.0 12.8 15.8": ["summat"], "23.9 7.4 13.5": ["gaudily"], "14.7 6.8 6.4": ["ipads"], "3.2 10.8 15.6": ["unmowed"], "5.2 0.7 13.2": ["sti"], "9.2 14.0 18.7": ["suburbanized"], "0.9 10.6 16.4": ["cmdlet"], "12.5 12.8 13.3": ["sapiens"], "11.4 15.4 13.8": ["fetchers"], "19.9 4.7 18.0": ["beechwood"], "11.5 10.9 25.6": ["fruitfly"], "9.8 12.3 3.8": ["unintelligibly"], "2.1 19.6 4.8": ["nanoviricide"], "11.7 18.5 8.3": ["untempered"], "13.9 11.8 18.8": ["woodchipping"], "10.7 16.3 14.3": ["souther"], "20.1 6.6 2.5": ["yeterday"], "7.7 5.3 31.9": ["cherimoya"], "7.0 16.1 10.7": ["bly"], "11.5 22.3 8.1": ["fairweather"], "-3.1 11.5 4.7": ["ulamas"], "10.4 5.8 18.2": ["leon"], "-4.1 9.8 -3.0": ["andto"], "5.9 7.8 8.1": ["neoclassicism"], "6.0 6.7 21.9": ["peahens"], "0.1 0.9 1.9": ["notarizing"], "13.6 -4.2 -0.8": ["reupped"], "6.8 12.1 8.7": ["pneumonic"], "1.7 14.9 16.4": ["singaporean"], "10.4 8.1 16.1": ["resod"], "3.4 10.1 9.4": ["grippier"], "10.2 2.1 14.5": ["papoose"], "3.7 8.1 4.7": ["catalyses"], "8.1 0.2 27.0": ["hardshell"], "4.9 -6.6 -1.5": ["anounce"], "5.8 -2.2 -4.5": ["appeard"], "1.6 4.1 11.1": ["atrophic"], "1.7 6.8 -1.6": ["telcagepant"], "4.0 0.7 13.6": ["bates"], "3.6 -1.3 -3.8": ["basedon"], "10.3 20.0 9.2": ["squareness"], "5.2 2.7 6.8": ["soundwall"], "16.2 15.8 8.1": ["klaxons"], "-0.3 -4.3 20.5": ["redecking"], "12.6 9.8 11.0": ["overcapitalized"], "7.6 6.9 14.4": ["diptychs"], "5.5 9.7 25.2": ["sugarbush"], "11.3 19.2 9.6": ["transcendently"], "7.0 1.2 -0.7": ["giftcards"], "11.2 0.2 1.0": ["thirdparty"], "1.0 3.9 5.7": ["luggages"], "13.0 0.2 0.0": ["hitech"], "10.8 10.3 16.2": ["windups"], "7.4 1.7 2.0": ["agencyfaqs"], "2.4 4.5 10.4": ["ofter"], "4.6 13.6 7.1": ["oblation"], "-2.8 5.4 7.4": ["demethylation"], "5.2 5.7 6.6": ["depolarization"], "5.8 2.9 11.5": ["biex"], "-4.7 6.8 5.6": ["ndi"], "19.1 -1.0 20.5": ["cruiseship"], "6.4 2.3 10.7": ["broadacre"], "7.0 10.9 11.9": ["uninventive"], "-3.9 23.8 0.1": ["designators"], "1.6 21.7 3.0": ["neuralgic"], "-11.8 1.2 4.9": ["thrombophilia"], "4.8 1.6 11.0": ["tams"], "6.9 17.1 1.7": ["leitmotiv"], "15.8 25.0 13.2": ["incorporeal"], "5.6 5.0 11.3": ["shmoozing"], "1.3 4.8 7.3": ["dyestuffs"], "17.2 -5.1 4.9": ["promotors"], "8.0 4.3 7.9": ["photomedicine"], "1.3 6.5 -2.0": ["teratogenic"], "4.0 20.1 -3.7": ["esteems"], "-2.8 5.3 8.0": ["recomputed"], "18.7 15.7 -1.9": ["oufit"], "-3.5 7.3 -0.0": ["hypoglycaemic"], "8.6 10.8 9.9": ["nanocapsules"], "15.8 12.1 18.0": ["lumbermen"], "4.2 15.8 13.6": ["mayweather"], "7.9 -6.1 16.0": ["superlongs"], "12.4 12.4 2.6": ["gladdening"], "6.9 -0.1 1.8": ["dfcu"], "5.6 17.5 7.7": ["nobodys"], "-2.6 7.7 10.2": ["pyar"], "-2.7 12.7 6.2": ["anomalism"], "13.7 24.9 16.6": ["ronin"], "-9.3 8.7 -0.8": ["procuracy"], "-10.7 14.1 -3.4": ["legatees"], "7.4 13.6 2.1": ["delousing"], "10.4 17.0 3.1": ["charlatanism"], "11.0 15.7 17.4": ["roundhouses"], "11.3 0.6 9.8": ["cablenet"], "17.8 26.6 14.3": ["poisoners"], "1.9 8.5 7.0": ["fic"], "8.8 11.2 9.7": ["ultracold"], "11.3 6.0 9.2": ["grupo"], "5.5 12.8 11.1": ["mishearing"], "4.5 2.5 7.1": ["deconsecrated"], "7.6 31.5 4.0": ["troups"], "-7.1 5.0 6.5": ["singlemode"], "3.4 10.8 10.6": ["aspergillus"], "-5.1 -0.7 6.6": ["mbbls"], "-3.7 15.6 -1.1": ["syndicalist"], "10.0 7.1 12.0": ["grinners"], "10.4 12.2 3.5": ["multizone"], "12.8 17.5 24.8": ["blackhead"], "7.0 11.8 31.1": ["avocets"], "6.9 19.4 10.1": ["piousness"], "13.8 2.3 2.2": ["nanosciences"], "19.6 4.0 7.0": ["counterbids"], "10.4 3.7 -1.5": ["inan"], "-3.9 0.2 2.4": ["bendamustine"], "-6.9 10.6 8.5": ["chid"], "2.7 -2.8 -2.9": ["offic"], "10.1 5.8 11.3": ["resodding"], "5.9 10.2 10.3": ["cra"], "-2.8 1.2 14.4": ["nongroup"], "3.5 23.5 9.6": ["ransoming"], "13.6 25.8 0.6": ["troublespot"], "10.2 -2.1 31.8": ["gastrique"], "4.7 0.1 10.5": ["haps"], "-3.4 3.9 13.1": ["hygenic"], "6.6 36.7 18.9": ["indiscriminant"], "6.9 11.3 12.0": ["roa"], "-0.5 11.9 3.2": ["differnce"], "23.3 12.3 15.7": ["blearily"], "7.3 8.1 7.4": ["geofence"], "5.3 9.5 11.7": ["ejectors"], "-1.3 20.2 5.7": ["ephemeris"], "7.6 4.0 5.3": ["junketing"], "4.1 15.6 5.3": ["ramjet"], "11.8 9.7 42.7": ["oystercatcher"], "3.3 10.2 4.8": ["ttm"], "7.6 17.4 9.8": ["reimaginings"], "-0.0 5.2 5.6": ["procuratorates"], "-0.7 20.0 1.8": ["countercoup"], "0.8 14.1 3.0": ["apposition"], "16.8 4.9 14.6": ["lipsticked"], "2.7 11.6 14.5": ["qtl"], "-6.4 3.0 -2.5": ["posttraumatic"], "1.3 15.2 8.9": ["ayah"], "16.8 11.4 19.0": ["gangplanks"], "7.7 17.4 15.6": ["crossly"], "6.2 5.9 13.0": ["adenoidal"], "16.5 11.2 12.6": ["carbuncles"], "-4.8 9.5 4.1": ["xxvii"], "13.2 3.0 15.8": ["doyennes"], "7.2 22.1 13.0": ["gound"], "23.4 3.5 -1.5": ["stateof"], "5.1 5.0 6.3": ["morpheme"], "2.1 3.1 9.7": ["holers"], "7.1 -2.0 13.9": ["connecticut"], "13.0 13.1 4.4": ["nervelessly"], "-1.1 5.8 7.1": ["prostatectomies"], "-2.8 9.2 -6.9": ["wiretappings"], "8.4 23.9 7.6": ["reprehensibly"], "-2.5 12.8 4.5": ["uncleanliness"], "10.4 5.4 3.3": ["hotzones"], "2.3 3.4 7.1": ["ceria"], "9.1 7.3 12.9": ["cairo"], "5.8 4.9 14.7": ["loanshark"], "5.0 9.5 -0.9": ["unostentatious"], "-1.3 11.1 11.5": ["underride"], "2.7 3.4 23.0": ["claire"], "-7.1 8.8 13.8": ["gali"], "14.4 14.5 9.6": ["pffft"], "11.5 6.0 -2.0": ["palmtops"], "10.2 13.9 8.3": ["tonking"], "7.8 5.1 14.1": ["masques"], "3.5 7.0 15.9": ["camis"], "-7.1 5.7 19.9": ["cavans"], "15.0 5.5 22.3": ["misshaped"], "13.7 6.0 19.6": ["endpapers"], "13.5 15.5 33.3": ["rapalas"], "5.8 18.7 12.2": ["combatively"], "-6.7 3.8 6.6": ["reappearances"], "-1.1 -0.9 10.6": ["worklife"], "5.6 4.6 10.9": ["biennales"], "20.4 21.4 47.8": ["sandworms"], "15.8 2.6 17.9": ["groovers"], "7.3 16.3 13.3": ["deathcore"], "5.2 1.5 3.8": ["cla"], "2.8 5.0 14.3": ["bakit"], "5.0 -1.2 2.2": ["clearence"], "9.9 -0.7 21.6": ["pourable"], "11.0 12.5 15.1": ["canyonlands"], "7.2 5.8 34.1": ["groundbait"], "-9.7 5.0 10.2": ["solemnizing"], "4.7 9.3 11.8": ["wigging"], "11.3 11.1 16.0": ["dipsticks"], "16.3 4.9 15.1": ["sunhat"], "0.3 7.3 7.1": ["naggingly"], "9.2 1.2 25.6": ["gerberas"], "5.2 6.9 12.5": ["stephanie"], "7.1 -2.4 1.1": ["annoucements"], "-1.1 -0.5 15.1": ["tmt"], "17.6 19.2 25.0": ["blowfly"], "-0.9 25.5 0.4": ["takfiris"], "10.3 13.1 2.1": ["nein"], "3.1 13.0 -1.7": ["stonefaced"], "4.0 7.4 12.7": ["postsynaptic"], "6.8 13.1 27.8": ["nonpoisonous"], "5.6 9.7 7.1": ["marchitecture"], "-0.9 9.0 25.6": ["deglazing"], "3.0 10.1 19.6": ["uri"], "7.7 1.7 -0.6": ["soigneur"], "10.7 3.5 4.4": ["immortalization"], "-4.6 0.7 -0.9": ["terbutaline"], "16.1 -0.2 18.5": ["knickerbockers"], "5.2 8.8 6.6": ["acetylcholinesterase"], "0.1 9.9 6.0": ["wantto"], "3.5 10.0 0.2": ["edoxaban"], "6.6 -0.2 4.1": ["chroming"], "4.5 -0.2 1.3": ["vps"], "-4.2 12.7 12.4": ["bhava"], "5.5 6.6 5.1": ["temped"], "2.8 8.4 17.0": ["guesstimating"], "12.0 8.7 0.0": ["dropside"], "-6.8 -4.3 1.4": ["eligiblity"], "5.9 17.6 10.6": ["equi"], "14.7 17.9 9.0": ["anaesthetise"], "12.1 5.4 8.2": ["chavvy"], "5.1 3.6 10.2": ["vari"], "-0.5 2.9 2.1": ["maintanence"], "4.2 7.0 13.1": ["mtr"], "-6.7 9.2 2.3": ["prefatory"], "4.0 1.7 3.2": ["neuen"], "21.5 16.7 25.5": ["moocher"], "-7.3 -1.7 -6.3": ["corrigendum"], "9.8 15.4 14.4": ["floppers"], "-10.2 14.7 4.9": ["coagulopathy"], "-1.5 1.6 7.3": ["bwpd"], "5.0 3.8 -0.8": ["invasively"], "14.2 7.0 17.6": ["cretaceous"], "-3.7 7.3 10.8": ["racebike"], "3.9 19.5 5.2": ["obdurately"], "10.9 5.7 28.0": ["corncrake"], "3.7 7.7 5.0": ["duduk"], "-1.6 -0.1 2.0": ["striatal"], "10.1 20.1 -5.3": ["challanges"], "2.7 18.2 14.5": ["dissin"], "7.5 18.7 3.9": ["formable"], "-5.9 9.9 6.4": ["nonurgent"], "-7.3 3.2 0.1": ["thalamic"], "3.0 15.0 8.2": ["smurfers"], "-5.3 -0.8 0.8": ["handwrote"], "-6.5 13.1 5.2": ["effectuation"], "17.9 19.9 13.7": ["whaddaya"], "12.5 1.2 9.1": ["apothecaries"], "5.8 4.6 8.2": ["sri"], "7.1 -1.4 5.7": ["cebr"], "-2.5 6.0 10.2": ["antibullying"], "1.7 10.8 5.1": ["transnationalism"], "8.8 13.8 12.8": ["angelically"], "-0.3 15.9 1.3": ["requiems"], "9.5 13.6 16.1": ["thangs"], "7.7 24.8 10.8": ["manoeuvers"], "-8.3 6.1 4.5": ["tricyclics"], "4.3 3.0 15.8": ["kada"], "6.8 4.0 17.5": ["faceting"], "9.8 5.7 3.6": ["bajaj"], "-5.5 5.4 2.7": ["franker"], "-3.0 10.0 14.6": ["nala"], "17.6 -0.9 -0.6": ["petrochemistry"], "2.5 10.9 13.3": ["stickbacks"], "9.7 18.9 13.9": ["chokeslams"], "-1.0 -9.3 11.0": ["nonhospital"], "13.8 8.3 9.5": ["optogenetics"], "4.5 15.4 30.2": ["chukars"], "19.5 1.8 10.3": ["peen"], "15.6 13.8 11.9": ["strimmer"], "7.8 12.0 11.2": ["austerities"], "10.9 18.7 8.6": ["yakkers"], "11.6 6.0 17.2": ["slipperier"], "11.7 2.3 6.5": ["beeb"], "10.2 24.9 8.8": ["heliopause"], "0.5 5.5 21.4": ["haymaking"], "-2.8 5.1 14.7": ["raat"], "-1.7 9.3 8.1": ["pretreating"], "15.3 7.6 23.7": ["budgerigars"], "8.3 10.6 12.0": ["dearie"], "6.3 -0.7 11.0": ["hx"], "23.1 4.6 8.6": ["peepshow"], "1.9 24.2 13.2": ["stupidness"], "0.1 8.5 5.7": ["geographics"], "5.3 7.4 3.5": ["triumverate"], "4.1 17.3 7.0": ["terminological"], "10.7 7.1 13.3": ["belvedere"], "6.3 5.6 9.0": ["quartzites"], "2.8 10.2 3.5": ["asterisked"], "-0.6 25.5 8.8": ["replayable"], "3.9 6.8 5.7": ["narrowbodies"], "12.7 2.9 29.7": ["woolies"], "8.9 1.7 9.4": ["triseries"], "-3.0 4.6 4.8": ["mux"], "6.9 1.8 19.6": ["feu"], "1.6 8.8 6.0": ["embryologists"], "16.1 5.8 8.1": ["chamfered"], "18.2 8.9 17.3": ["wormery"], "17.3 1.2 11.4": ["theatreland"], "-0.2 4.7 9.9": ["usted"], "3.9 13.3 3.0": ["striaght"], "16.7 31.9 1.8": ["neocolonialist"], "-8.6 8.8 6.9": ["bey"], "4.0 1.5 13.6": ["eau"], "6.0 7.2 11.4": ["nashville"], "5.8 6.2 -3.9": ["ghostwrite"], "7.0 16.9 8.2": ["parodist"], "21.6 2.2 9.6": ["pepsi"], "-4.3 10.7 4.5": ["devaluated"], "-0.8 7.9 6.0": ["userspace"], "16.8 9.2 10.0": ["inconsolably"], "5.5 15.1 6.9": ["initializes"], "-1.3 4.5 6.4": ["nonsupervisory"], "0.6 17.6 15.3": ["commodores"], "11.9 8.9 17.5": ["harrows"], "9.7 9.3 2.5": ["socialises"], "2.7 1.2 23.6": ["dahl"], "8.0 17.2 6.5": ["otherwords"], "-3.7 5.4 4.4": ["hypotensive"], "-1.6 6.9 -0.2": ["ivabradine"], "-9.0 1.9 6.1": ["gastrectomy"], "12.4 15.1 11.6": ["doorposts"], "-1.3 2.6 2.3": ["olaparib"], "-2.7 17.7 4.9": ["mahram"], "7.8 30.4 4.6": ["milita"], "4.2 8.3 10.7": ["tzitzit"], "4.9 12.3 5.3": ["unwaged"], "-0.9 20.9 5.5": ["subtextual"], "11.8 12.2 49.1": ["threadfins"], "7.9 7.1 19.1": ["monochromes"], "7.9 9.1 11.8": ["oes"], "-1.1 8.2 0.2": ["transpark"], "8.1 8.0 16.8": ["voguing"], "2.5 5.3 9.4": ["speedups"], "14.7 19.2 4.7": ["externalise"], "3.7 -1.5 15.1": ["largo"], "-2.4 8.2 2.0": ["neuroinflammation"], "8.4 6.7 7.5": ["buscones"], "4.7 -0.2 6.1": ["rised"], "6.2 7.1 11.7": ["ull"], "-6.0 8.6 0.9": ["enquirers"], "0.3 8.1 11.5": ["stepgrandson"], "0.7 3.2 9.9": ["diffs"], "-1.3 2.6 8.0": ["dehydrogenase"], "17.4 11.3 44.8": ["amberjacks"], "3.0 3.7 9.6": ["anemically"], "17.3 5.2 8.8": ["tourbus"], "10.7 4.5 12.2": ["preannouncements"], "0.4 -1.2 -0.2": ["ict"], "11.1 25.5 13.1": ["destructor"], "-3.1 14.6 8.5": ["unpaged"], "1.1 20.0 11.6": ["kidology"], "6.6 17.5 17.1": ["hydrophobia"], "3.8 1.8 5.0": ["overburdens"], "-11.3 12.8 1.5": ["yahrzeit"], "17.3 28.5 9.7": ["lancer"], "-4.8 10.7 9.4": ["constitutents"], "9.8 7.2 17.7": ["untradable"], "9.8 10.5 14.0": ["warmings"], "4.6 8.4 17.7": ["bruh"], "8.3 8.2 8.4": ["tachometers"], "1.6 4.5 6.3": ["forclosure", "erythropoietins"], "6.5 6.7 12.4": ["festivites"], "19.5 2.5 14.2": ["ampitheater"], "-3.7 11.1 -2.8": ["safeness"], "-4.2 12.7 0.8": ["seldomly"], "2.9 6.0 20.7": ["uli"], "21.4 22.5 15.0": ["borg"], "1.8 11.8 8.0": ["beltways"], "16.2 11.4 32.1": ["lingonberry"], "12.1 10.9 13.1": ["powerbook"], "-7.0 3.7 13.9": ["imiglucerase"], "8.9 -1.9 17.5": ["eft"], "13.8 19.2 15.8": ["hiptoss"], "5.7 12.5 15.6": ["tryed"], "6.8 17.6 9.6": ["unyieldingly"], "8.0 14.2 -1.3": ["aggrandized"], "-6.9 7.3 -0.2": ["thn"], "13.9 3.4 15.2": ["pressie"], "14.1 8.1 2.9": ["rejuvinated"], "-3.4 -0.7 0.8": ["repaglinide"], "17.0 3.1 -0.7": ["cardiogram"], "7.9 17.2 12.7": ["blabbermouths"], "-4.3 9.1 0.8": ["oppotunity"], "-1.2 5.1 7.8": ["upconverter"], "3.2 18.0 4.1": ["geotags"], "-0.5 7.8 1.3": ["wailings"], "0.7 5.8 -5.6": ["tnn"], "15.8 19.8 23.9": ["blowflies"], "4.0 11.5 2.2": ["momemtum"], "7.2 8.8 47.9": ["shovelnose"], "1.0 10.3 1.4": ["soemthing"], "11.9 -1.9 4.7": ["proj"], "-2.6 -4.6 17.5": ["breedings"], "15.3 23.8 8.0": ["ineffectuality"], "23.2 14.6 3.9": ["chuffing"], "15.2 17.2 15.8": ["amazingness"], "14.2 9.3 13.4": ["hotty"], "-2.6 -0.4 11.8": ["hooper"], "-1.4 10.9 -0.7": ["defibrillated"], "8.1 6.8 3.9": ["hacer"], "18.8 2.9 15.2": ["cremes"], "9.4 15.2 20.5": ["stratus"], "6.3 0.3 14.7": ["cham"], "4.6 9.2 5.0": ["conservativeness"], "-1.4 5.0 36.0": ["clammer"], "3.7 4.4 14.0": ["scheelite"], "31.7 2.9 4.8": ["secondlargest"], "10.4 6.3 25.0": ["teaspoonfuls"], "15.3 8.2 2.6": ["staticky"], "5.7 6.4 7.8": ["dihydrotestosterone"], "0.1 10.1 14.7": ["nverstop"], "7.6 3.2 29.5": ["aku"], "0.9 5.9 14.1": ["comminution"], "12.3 15.7 18.6": ["snowmageddon"], "7.1 10.5 42.4": ["eiders"], "5.3 12.1 7.0": ["rescanning"], "-1.1 21.8 3.4": ["overdramatize"], "17.2 15.8 21.9": ["lifebuoy"], "11.8 10.7 -0.6": ["analagous"], "11.8 7.1 28.9": ["carmel"], "3.3 11.5 11.2": ["reprobation"], "23.0 12.1 26.9": ["fatted"], "15.6 12.3 17.0": ["grandmama"], "4.6 8.7 3.1": ["collission"], "-10.5 -7.8 3.0": ["precollege"], "7.1 2.9 10.7": ["afternon"], "15.4 10.8 8.6": ["arrivistes"], "12.3 9.3 5.4": ["broadsiding"], "19.1 19.7 11.7": ["rotter"], "4.9 15.3 -2.3": ["cluing"], "2.2 15.1 4.3": ["inertness"], "8.2 25.8 7.3": ["recalcitrants"], "4.5 -2.0 7.5": ["biomechanist"], "3.8 12.6 11.1": ["wut"], "-2.0 0.2 12.8": ["gst"], "10.7 6.2 34.1": ["saganaki"], "1.7 5.8 11.2": ["nonoil"], "0.7 12.9 13.5": ["reoppose"], "4.3 -1.0 12.6": ["platinums"], "8.8 -5.7 0.8": ["afteroon"], "-1.0 7.7 12.1": ["epithelia"], "14.6 3.1 9.3": ["bajo"], "0.4 1.2 21.5": ["khoya"], "14.6 4.2 6.2": ["uncompelling"], "13.3 9.9 9.0": ["gifs"], "5.0 21.3 8.8": ["mormons"], "-1.9 7.1 2.0": ["remediates"], "-0.1 -0.8 -4.3": ["rereleasing"], "7.2 1.7 1.4": ["clas"], "4.5 11.3 7.7": ["rtm"], "9.4 21.5 9.9": ["imbiber"], "11.2 3.2 20.4": ["coffe"], "2.5 8.4 2.5": ["pris"], "7.8 6.4 20.1": ["taupes"], "14.7 6.3 19.8": ["paunches"], "5.0 9.5 11.6": ["usally"], "5.2 -3.9 16.3": ["artwalk"], "-3.3 28.6 4.8": ["taqiyya"], "20.6 -3.1 16.0": ["boomtime"], "8.6 0.2 11.7": ["skiiing"], "-3.6 10.6 8.1": ["informatively"], "-5.0 7.6 7.7": ["enuresis"], "14.8 18.7 8.1": ["cyberthieves"], "15.4 29.5 8.0": ["conquerer"], "1.0 3.2 12.0": ["nonuniform"], "4.8 -0.3 9.1": ["eer"], "10.7 11.8 7.9": ["handsy"], "2.6 45.0 9.4": ["fragged"], "-0.8 23.1 6.8": ["ironist"], "7.0 6.1 10.1": ["shoegazers"], "-3.1 7.7 8.4": ["malocclusion"], "-3.1 -1.8 5.4": ["undercompensated"], "3.5 -3.0 7.3": ["mandola"], "4.8 23.0 12.5": ["suckiness"], "8.1 8.1 8.9": ["nextdoor"], "3.1 8.9 19.8": ["soakings"], "14.9 10.4 41.0": ["staghorn"], "13.7 1.0 1.6": ["shopfitting"], "12.9 2.9 10.3": ["schlumpy"], "14.0 12.8 28.3": ["blueish"], "12.5 5.5 12.0": ["hault"], "6.0 10.2 16.9": ["haffi"], "-1.3 4.5 6.7": ["punjab"], "9.8 3.4 1.1": ["prefunded"], "15.9 13.6 10.4": ["loooooong"], "3.1 26.6 7.8": ["decencies"], "25.2 4.4 27.4": ["lamington"], "7.1 1.0 6.3": ["lifecasting"], "6.0 10.8 8.6": ["impishness"], "12.6 5.3 9.7": ["classlessness"], "11.0 2.7 23.2": ["sloshy"], "-2.6 3.3 2.4": ["pbxnsip"], "12.0 12.9 9.0": ["garbling"], "21.1 -9.3 9.0": ["thelargest"], "18.1 20.0 5.1": ["begone"], "-1.6 12.1 4.6": ["exaction"], "5.0 4.4 14.0": ["wes"], "4.1 17.5 4.8": ["dissapeared"], "12.1 -2.0 1.7": ["acetyls"], "6.9 2.6 20.9": ["chophouse"], "13.1 4.9 24.2": ["saucepot"], "18.4 14.7 9.2": ["veritas"], "12.3 17.5 7.9": ["ideaviruses"], "6.1 13.9 0.3": ["stiflingly"], "14.6 2.3 3.3": ["oxyfuel"], "4.7 12.1 10.9": ["stiction", "zack"], "2.1 -2.6 13.9": ["chemises"], "6.9 13.3 15.5": ["whipsaws"], "5.3 15.9 20.8": ["epiphytes"], "14.7 6.7 17.8": ["grandads"], "-7.2 9.5 2.0": ["oesophagectomy"], "13.2 21.3 3.8": ["synecdoche"], "11.4 22.2 15.1": ["nooo"], "-3.9 11.2 5.0": ["pedagogies"], "-1.4 14.3 4.0": ["corruptibility"], "6.2 5.6 5.9": ["icrossing"], "-1.3 10.6 0.9": ["transistion"], "6.6 26.2 9.3": ["unequals"], "10.3 7.1 17.0": ["archipelagoes"], "9.6 14.0 14.4": ["aroung"], "8.4 41.0 7.2": ["garrisoning"], "18.3 9.0 19.6": ["scrunchy"], "7.6 7.5 11.4": ["sassiest"], "10.8 4.5 22.9": ["cloisonne"], "-9.9 1.5 11.0": ["sternotomy"], "5.0 4.6 3.6": ["eam"], "-0.4 22.5 3.1": ["sacrafice"], "-6.3 9.8 -4.7": ["haq"], "10.3 11.2 22.3": ["teosinte"], "-1.7 3.5 3.1": ["harking"], "-5.4 -4.5 8.4": ["courseload"], "3.1 5.3 15.5": ["cattles"], "3.0 7.6 8.6": ["echt"], "11.3 6.4 39.5": ["tomatoey"], "7.3 18.2 7.2": ["unalienating"], "3.4 7.9 8.5": ["togo"], "5.2 13.5 6.3": ["microlenses"], "-7.5 4.1 4.6": ["hammams"], "11.7 15.1 14.0": ["rewilding"], "-5.8 14.3 5.1": ["aminoglycosides"], "4.5 23.8 -4.1": ["unifiers"], "6.5 8.0 23.8": ["thinnings"], "-6.0 -1.5 2.5": ["vation"], "19.0 27.1 21.7": ["whap"], "26.6 6.7 15.0": ["squeezy"], "3.2 15.9 4.6": ["claustrophobically"], "15.1 12.2 10.3": ["waze"], "4.5 4.6 3.4": ["keine"], "5.8 5.9 12.1": ["jia"], "8.1 17.3 5.7": ["keitai"], "13.4 8.2 11.9": ["buttload"], "17.3 25.3 4.8": ["housetops"], "2.3 -4.4 18.3": ["winetasting"], "16.8 7.9 21.4": ["masticated"], "16.1 -0.1 18.8": ["marquise"], "0.0 16.7 5.6": ["paramagnetic"], "12.0 -2.1 13.9": ["polyvinyl"], "4.2 7.4 16.8": ["refroze"], "0.8 10.6 7.1": ["genlock"], "9.3 20.5 15.4": ["leatherneck"], "8.5 9.1 4.1": ["lecturn"], "-2.5 13.1 20.3": ["supertasters"], "5.5 2.6 10.4": ["lce"], "8.1 13.7 5.9": ["diopter"], "0.1 2.7 18.2": ["piercers"], "5.0 8.9 7.7": ["thatare"], "11.7 2.1 21.2": ["smorgasboard"], "-12.2 8.7 8.5": ["noncapital"], "-4.6 12.9 -9.5": ["reemphasizing"], "5.9 1.8 5.4": ["sistema"], "3.8 1.0 7.4": ["magstripe"], "9.7 1.7 2.1": ["refiles"], "12.4 16.6 11.3": ["airhorn"], "-6.6 9.8 2.9": ["communitys"], "5.0 4.8 7.6": ["rechannel"], "7.4 8.3 4.0": ["aparently"], "15.4 13.6 11.7": ["pillories"], "16.3 13.2 7.2": ["videogamers"], "8.9 8.0 1.0": ["refuellers"], "15.8 15.8 6.6": ["ungraciously"], "3.0 8.4 22.2": ["tarter"], "8.0 17.0 27.2": ["refugia"], "6.0 12.6 2.8": ["homewards"], "20.4 8.6 11.3": ["fatcat"], "-3.0 -4.6 1.8": ["alc"], "-0.5 0.9 13.0": ["upcounty"], "2.5 8.1 0.1": ["valuate"], "14.3 7.1 8.5": ["prettying"], "14.6 9.8 9.3": ["babydaddy"], "16.2 7.4 14.8": ["phyto"], "-8.1 7.5 0.9": ["auxilliary"], "12.4 13.2 6.8": ["indiscreetly"], "1.8 6.6 24.7": ["ampalaya"], "2.2 4.3 10.0": ["jeong"], "3.6 5.9 33.8": ["bresaola"], "-8.0 16.8 1.9": ["repect"], "-0.3 4.8 3.4": ["xt"], "1.3 16.3 9.0": ["contrasty"], "24.3 15.2 33.4": ["trilobite"], "13.9 13.6 14.2": ["grift"], "-5.0 1.2 3.9": ["pend"], "5.7 3.0 3.5": ["opf"], "11.6 17.0 21.5": ["huracanrana"], "15.9 12.9 11.3": ["neverland"], "4.9 6.4 10.7": ["cvs"], "1.2 10.0 16.6": ["densify"], "16.7 16.7 27.6": ["goannas"], "13.1 3.0 7.4": ["chatline"], "4.5 18.2 7.4": ["veeps"], "7.6 5.6 8.4": ["falloffs"], "-0.1 3.3 2.4": ["hemiplegia"], "-6.6 9.0 1.7": ["victimizations"], "8.6 8.7 16.5": ["rosie"], "14.5 9.4 11.4": ["technophobia"], "21.6 27.2 16.2": ["lifeform"], "3.7 6.8 3.1": ["mpm"], "11.1 11.9 16.7": ["stripling", "appared"], "-6.1 2.8 8.3": ["detoxes"], "-3.5 4.0 1.1": ["haemophiliac"], "20.2 8.6 15.5": ["slingin"], "-0.3 6.6 14.8": ["rimfire"], "5.4 22.4 12.3": ["devestation"], "23.6 7.1 18.6": ["rotisseries"], "8.2 16.6 10.3": ["inamorata"], "-1.9 17.7 2.4": ["equerry"], "5.4 4.9 15.5": ["leafier"], "8.3 18.0 17.2": ["coarsest"], "8.3 19.0 9.1": ["collectivisation"], "5.2 11.3 21.5": ["poultries"], "3.3 1.5 1.7": ["subservicing"], "-5.1 6.9 9.0": ["disincorporation"], "4.1 12.3 6.7": ["exothermic"], "-3.2 11.6 3.9": ["vituperations"], "7.9 7.1 46.2": ["jewfish"], "8.0 10.7 7.3": ["adenovector"], "12.6 10.6 8.2": ["bethe"], "9.9 13.1 16.2": ["ronnie"], "7.9 8.6 24.3": ["dogsleds"], "21.1 -3.1 13.7": ["petfood"], "9.3 5.7 8.5": ["footboards"], "9.8 -7.8 2.5": ["retendering"], "27.9 7.1 9.1": ["zoetrope"], "14.5 24.3 18.4": ["mocker"], "9.1 14.6 6.0": ["wherewithall"], "-4.1 0.5 8.5": ["dijo"], "0.7 5.3 8.9": ["cathy"], "7.1 11.4 9.4": ["freestyled"], "8.0 7.4 3.3": ["tribology"], "7.1 9.6 12.4": ["stayaways"], "22.9 11.8 10.2": ["janky"], "0.6 -7.1 6.6": ["ewd"], "7.2 7.0 12.2": ["loopiness"], "-8.6 17.8 5.9": ["quran"], "-2.0 9.1 3.0": ["extradicted"], "4.6 6.4 9.5": ["endograft"], "14.9 8.4 7.9": ["chrysler"], "2.0 23.8 9.6": ["dybbuk"], "13.9 14.2 5.5": ["papercraft"], "11.3 3.4 4.0": ["ballgirls"], "15.2 5.6 27.8": ["spumoni"], "11.3 13.3 8.7": ["gesticulates"], "2.6 18.3 3.7": ["liberationist"], "4.8 8.1 18.3": ["propellent"], "4.6 10.2 3.8": ["reexamines"], "22.8 32.9 16.0": ["petrify"], "10.2 -1.3 16.2": ["lum"], "-8.2 7.1 6.5": ["igxglobal"], "3.2 2.9 0.6": ["decompresses"], "15.7 18.3 2.3": ["mindspace"], "-5.7 11.8 -2.9": ["especailly"], "-8.9 7.0 0.3": ["psychoeducation"], "5.1 0.4 11.7": ["wallace"], "16.1 13.7 15.3": ["monocles"], "12.7 30.1 10.4": ["evildoing"], "6.7 14.9 25.5": ["undomesticated"], "-5.4 10.1 0.9": ["gell"], "-8.5 2.9 1.4": ["fluvastatin"], "13.5 2.9 14.3": ["grans"], "-3.2 8.8 8.4": ["lysosomal"], "4.3 10.5 12.2": ["bahus"], "2.8 3.9 6.5": ["meloxicam"], "-8.4 -0.3 13.6": ["tikina"], "18.9 34.2 13.7": ["tyrannous"], "6.9 17.2 4.2": ["atomisation"], "1.7 0.4 2.7": ["universitys"], "6.8 12.6 8.0": ["firecrews"], "24.1 7.5 19.5": ["bewhiskered"], "-2.2 4.8 8.3": ["posi"], "-1.3 11.5 7.7": ["ungovernability"], "3.1 18.9 3.5": ["mistranslations"], "-1.1 8.6 16.5": ["macrobiotics"], "9.9 9.3 9.6": ["slummy", "tractortrailer"], "3.5 10.7 6.9": ["ats"], "4.6 5.2 14.1": ["itanium"], "5.4 5.1 2.8": ["ungeared"], "26.1 29.4 14.7": ["ravening"], "10.0 6.1 33.7": ["muffuletta"], "7.6 14.8 13.0": ["unsocialized"], "15.5 5.6 11.1": ["rumbas"], "-0.7 6.6 7.6": ["allotees"], "11.2 16.4 2.2": ["ridded"], "-7.4 15.9 13.0": ["monastics"], "0.3 9.5 13.5": ["prokaryotic"], "-6.1 11.2 -3.9": ["heresay"], "1.4 0.1 13.5": ["nak"], "13.8 0.3 7.4": ["centro"], "4.5 2.9 8.5": ["erratum"], "7.9 8.2 15.5": ["neckband"], "5.9 18.0 12.1": ["dispair"], "8.9 11.7 13.9": ["ura"], "21.6 2.1 12.6": ["tinkly"], "8.3 17.2 4.7": ["downloadables"], "7.9 -3.7 13.9": ["paperboards"], "8.6 3.6 6.0": ["fash"], "1.6 10.4 4.1": ["highsided"], "13.7 8.6 6.6": ["preselling"], "-1.9 7.3 7.5": ["catabolism"], "-8.8 -1.9 4.7": ["recomendation"], "-3.1 14.1 7.8": ["standdown"], "13.4 6.3 15.1": ["headin"], "8.3 16.1 24.1": ["fale"], "13.2 12.3 20.2": ["pitman"], "12.9 21.6 3.9": ["everchanging"], "16.7 4.4 33.5": ["poppadoms"], "3.3 11.8 -2.6": ["posibility"], "-1.4 25.3 2.2": ["rigidness"], "-10.4 -1.2 17.5": ["micronaire"], "9.1 8.3 16.2": ["dumbo"], "5.0 14.5 31.4": ["milkweeds"], "11.5 4.7 20.4": ["mou"], "12.3 16.9 3.7": ["gutwrenching"], "-6.0 5.7 11.6": ["chidlren"], "2.0 9.9 7.6": ["handsomer"], "18.1 10.7 4.1": ["rubbishy"], "11.9 5.7 20.2": ["slenderness"], "0.3 6.1 13.7": ["slacklining"], "13.8 2.5 12.0": ["snowmaker"], "7.9 2.7 44.0": ["escabeche"], "13.0 0.3 13.9": ["palazzos"], "0.4 7.1 6.3": ["ixabepilone"], "2.0 17.7 8.2": ["corpers"], "12.9 5.4 5.4": ["coronagraph"], "19.8 10.9 24.2": ["pigmy"], "4.1 3.9 16.5": ["containerisation"], "3.5 8.0 13.1": ["bonders"], "3.0 2.1 -4.4": ["telepharmacy"], "7.3 11.8 14.3": ["msconfig"], "10.2 16.9 4.7": ["spaceborne"], "2.9 2.5 13.5": ["allergenicity"], "-1.6 15.6 12.5": ["flirtatiousness"], "10.0 15.6 8.4": ["stonger"], "-1.9 0.8 3.1": ["lispro"], "4.9 -2.5 2.7": ["defreeze"], "6.7 19.3 32.9": ["quaggas"], "-1.3 6.0 14.6": ["triactor"], "10.3 8.8 30.1": ["tofurkey"], "0.6 8.3 1.9": ["inkers"], "19.8 -3.6 15.5": ["beano"], "9.7 23.3 9.1": ["obscuration"], "17.5 6.9 12.5": ["tennies"], "5.0 -2.4 11.9": ["pianoforte"], "4.0 -4.0 7.1": ["restringing"], "5.5 14.6 16.6": ["devine"], "1.8 7.6 7.7": ["anxiolytic"], "-2.7 3.6 12.0": ["debulking"], "-5.1 20.2 8.2": ["familiarities"], "-2.6 4.6 -0.3": ["behalves"], "15.4 17.9 10.9": ["undetonated"], "17.0 7.1 -7.3": ["wordwide"], "-1.5 4.0 8.8": ["satiates"], "15.6 1.4 5.0": ["paned"], "11.5 23.8 6.9": ["moronically"], "-0.2 6.1 3.3": ["reargument"], "2.1 7.9 13.3": ["globals"], "1.4 3.0 12.8": ["ayo"], "17.4 1.5 -1.9": ["thetop"], "-8.6 13.3 10.0": ["concelebrants"], "19.3 -2.2 27.4": ["wingding"], "18.6 5.2 24.8": ["cloudlike"], "11.7 15.7 2.9": ["sweetspot"], "13.4 20.4 20.4": ["whaled"], "8.5 14.7 4.1": ["competitior"], "5.3 10.0 7.2": ["denotify"], "8.9 2.9 13.6": ["upholsterers"], "6.5 23.6 0.1": ["antipathetic"], "4.2 -1.0 6.5": ["succinate"], "12.4 21.1 21.8": ["denseness"], "-1.5 7.3 8.1": ["granularly"], "2.8 -2.5 17.9": ["greenmarket"], "0.7 7.1 2.1": ["unsubordinated"], "5.9 33.3 3.6": ["misunderestimate"], "1.9 8.7 1.7": ["gridder"], "9.3 13.6 11.3": ["bookmarklets"], "6.3 12.9 17.5": ["lunchpail"], "5.9 0.8 14.2": ["doublets"], "-1.1 14.7 4.9": ["unities"], "-3.7 4.5 13.7": ["codas"], "9.6 10.0 7.5": ["uraniferous"], "-0.8 10.0 6.7": ["postulant"], "-6.4 12.6 6.7": ["recompilation"], "5.7 -2.7 13.0": ["firstrun"], "23.4 7.8 -2.0": ["emblazoning"], "8.6 21.4 5.6": ["supressing"], "13.0 12.2 14.8": ["boyo"], "10.8 14.4 17.4": ["smithing"], "2.4 -4.9 8.9": ["buydowns"], "5.6 -4.1 13.7": ["dbl"], "-1.4 11.1 13.5": ["unreinforced"], "19.6 7.9 11.8": ["dustcart"], "-7.2 -6.0 9.6": ["eligibilty"], "15.9 4.0 4.2": ["steeplejack"], "0.2 -1.4 10.2": ["dalawang"], "5.4 9.7 4.5": ["balancesheet"], "11.4 4.6 4.7": ["kybosh"], "7.2 11.9 7.1": ["rebelliously"], "4.5 -3.5 11.1": ["wb"], "17.5 15.2 13.9": ["crippler"], "12.5 15.0 22.7": ["discolors"], "-1.6 8.1 6.1": ["enzastaurin"], "-2.4 13.4 7.2": ["outbowled"], "3.6 16.2 -2.2": ["conduce"], "4.9 4.9 13.5": ["nautanki"], "4.8 22.6 10.5": ["fixity"], "20.1 -5.2 22.0": ["kahuna"], "7.3 5.5 30.3": ["chokecherries"], "1.6 6.0 11.3": ["congenially"], "1.7 3.7 13.0": ["jol"], "-11.7 -2.0 12.3": ["solderability"], "1.1 15.8 12.7": ["careerwise"], "12.5 8.1 4.6": ["souce"], "2.2 -1.2 9.1": ["uteri"], "-7.7 10.7 16.0": ["turfgrasses"], "5.2 1.5 7.8": ["outrated"], "13.0 7.0 31.5": ["mustardy"], "10.2 0.3 10.2": ["salesrooms"], "-3.2 7.9 6.4": ["meningoencephalitis"], "7.3 14.8 26.1": ["bioregion"], "-6.0 14.1 1.2": ["overperform"], "-0.2 7.1 -1.9": ["dissatisfactory"], "15.2 4.3 18.5": ["woodchopping"], "11.8 16.5 8.6": ["kindof"], "8.2 7.3 12.0": ["incoordination"], "17.2 7.2 2.0": ["dollmaker"], "-3.5 3.4 16.8": ["backwardated"], "12.9 30.8 8.4": ["bloodsoaked"], "3.0 10.8 27.1": ["hulling"], "12.9 14.7 14.8": ["contemplatively"], "-2.5 4.5 10.3": ["tintypes"], "15.5 16.5 13.0": ["phillies"], "15.5 4.7 13.4": ["pikers"], "-6.4 -1.5 0.3": ["chairlady"], "7.3 14.7 8.8": ["exterminations"], "8.2 5.8 6.6": ["embroils"], "0.5 7.4 7.3": ["arrondissements", "intraluminal"], "8.7 14.6 2.5": ["taz"], "19.2 18.2 13.8": ["extrasolar"], "3.1 11.0 7.5": ["linebreaks"], "4.7 18.1 15.2": ["gutsiness"], "2.6 17.0 20.1": ["grampa"], "7.9 11.5 -0.6": ["heliocentric"], "8.6 24.8 4.9": ["griefers"], "-6.9 10.0 4.6": ["pyaar"], "2.0 3.6 22.3": ["cau"], "-1.1 2.7 2.7": ["reanalyzing"], "0.8 9.8 6.3": ["taxations"], "3.8 1.0 4.1": ["thriftiest"], "15.0 11.9 27.6": ["hamantaschen"], "7.5 10.0 7.4": ["inclinometer"], "-2.3 6.2 8.6": ["tabards"], "7.4 10.8 20.4": ["nonskid"], "17.4 7.1 16.8": ["lawnchairs"], "-1.3 14.2 19.9": ["wryness"], "-0.0 6.1 5.8": ["dataguise"], "18.4 18.3 29.3": ["fuzzball"], "17.7 13.6 12.6": ["scudding"], "6.4 7.9 39.2": ["saugeyes"], "4.1 1.9 4.7": ["bonder"], "11.5 2.5 26.5": ["redware"], "-3.4 2.1 12.0": ["offhire"], "2.7 7.2 13.9": ["palmer"], "1.9 12.3 12.3": ["discombobulation"], "12.8 9.0 29.2": ["pinkness"], "13.2 16.5 14.5": ["feckin"], "11.5 2.4 8.3": ["cualquier"], "13.4 0.5 9.1": ["inkless"], "8.6 1.8 7.5": ["brisbane"], "8.9 22.3 11.5": ["acrophobia"], "5.3 11.9 -0.4": ["subornation"], "3.6 6.7 45.8": ["spearfish"], "5.7 17.3 25.9": ["hammerfists"], "2.9 6.5 11.3": ["maltitol"], "1.8 9.2 37.4": ["shoyu"], "6.1 7.4 6.7": ["hiting"], "19.7 14.9 15.6": ["stoney"], "6.1 4.0 -0.2": ["flyaround"], "9.6 -6.0 0.8": ["screenprinted"], "7.8 4.8 4.3": ["cabbed"], "10.3 -9.8 -2.0": ["currrently"], "23.6 2.7 28.9": ["baps"], "-6.0 4.0 2.2": ["reauthorizations"], "15.0 6.3 0.5": ["remindful"], "10.2 15.2 7.5": ["arnt"], "10.1 4.6 12.7": ["guzheng"], "-0.2 7.5 6.0": ["crystallinity"], "6.1 2.9 26.6": ["capelet"], "12.3 15.2 23.2": ["jonquils"], "-6.6 8.2 12.7": ["forskolin"], "-9.8 7.6 -1.0": ["eparchy"], "7.2 11.5 41.7": ["brothy"], "4.6 13.0 16.4": ["brahmins"], "13.1 6.9 14.7": ["greywacke"], "10.5 9.8 21.5": ["firkin"], "12.1 16.2 12.7": ["scrollwheel"], "14.7 10.9 5.0": ["salesclerks"], "8.1 18.1 2.4": ["henceforward"], "3.9 1.8 5.5": ["scleral"], "16.2 8.2 14.9": ["tatt"], "-3.7 37.6 14.0": ["playstyle"], "-3.7 13.9 7.8": ["hamara"], "-3.3 8.0 11.5": ["giardiasis"], "3.9 16.9 33.1": ["hindquarter"], "6.3 17.8 8.9": ["dorkiness"], "4.1 11.1 7.9": ["beltholder"], "14.5 7.9 1.2": ["restructing"], "-5.3 9.3 7.0": ["polycythemia"], "-5.9 8.5 5.1": ["parenchymal"], "6.5 26.0 13.9": ["fatalists"], "4.3 25.7 12.0": ["helpmates"], "8.5 4.3 2.7": ["substitue"], "17.7 9.9 -2.0": ["monopolises"], "15.0 8.8 17.2": ["himbo"], "2.9 28.7 4.0": ["serviceperson"], "12.6 -1.0 0.3": ["recrafted"], "-9.4 6.8 -0.8": ["deas"], "17.6 8.3 22.5": ["campanile"], "-3.9 9.2 -2.5": ["organistion"], "5.0 14.8 9.5": ["blocklist"], "6.7 17.7 16.9": ["tito"], "19.1 20.3 11.2": ["ectoplasmic"], "17.4 9.3 10.7": ["gatecrashes"], "18.1 3.8 22.4": ["grahams"], "10.7 10.4 6.2": ["alkalis"], "-5.7 17.1 2.8": ["happended"], "7.0 8.8 15.0": ["nid"], "7.7 5.8 7.4": ["tappets"], "16.5 10.9 6.6": ["superclusters"], "26.6 4.2 7.9": ["amajor"], "9.9 3.9 11.3": ["lushest"], "7.5 7.3 8.9": ["ritalin"], "18.3 -0.8 0.1": ["derivate"], "2.5 10.9 14.8": ["rojiblancos"], "7.0 -5.0 3.2": ["microcredits"], "11.5 25.0 5.9": ["destory"], "2.0 15.4 4.4": ["patria"], "-2.0 6.1 22.7": ["ballasting"], "7.0 6.8 38.7": ["bagoong"], "-1.9 -1.7 11.1": ["burstable"], "1.5 2.2 15.8": ["concelebrating"], "7.6 16.8 8.4": ["bronchioles"], "-4.6 8.2 12.8": ["nucleosides"], "2.3 14.6 11.7": ["transship"], "-2.1 0.7 6.5": ["aztreonam"], "17.8 4.8 3.6": ["metronomes"], "5.8 7.2 6.3": ["chmodded"], "2.4 10.9 10.8": ["snowshoed"], "8.5 7.3 13.3": ["candela"], "11.7 3.6 17.1": ["pomeranian"], "19.5 6.5 14.7": ["flyspeck"], "-9.5 1.9 3.4": ["seronegative"], "-1.3 12.5 2.7": ["attoseconds"], "0.3 16.1 0.1": ["cognisable"], "0.6 4.6 19.6": ["autobody"], "12.3 3.8 10.9": ["amb"], "3.6 20.3 10.4": ["pettiest"], "-2.0 7.4 5.8": ["hatke"], "3.1 6.9 7.4": ["trackster"], "-6.6 -10.4 3.1": ["chool"], "6.4 11.4 25.9": ["nilgai"], "1.6 19.6 20.6": ["smiler"], "6.5 5.2 7.1": ["dimethyl"], "6.7 6.3 13.3": ["seepages"], "11.1 0.4 21.2": ["cappucino"], "0.3 -2.3 6.5": ["truckdriver"], "3.9 16.9 0.1": ["contries"], "-1.5 6.2 4.0": ["closeknit"], "13.2 11.2 8.5": ["louvre"], "13.8 11.7 13.8": ["weedeater"], "12.3 -2.4 16.5": ["muumuus"], "-3.8 16.5 8.2": ["unalike"], "20.7 14.6 5.6": ["toiler"], "7.4 12.6 12.6": ["dissapear"], "13.9 5.5 12.3": ["fantasias"], "-0.8 16.7 8.9": ["referents"], "4.0 26.9 13.1": ["shirker"], "2.3 2.2 1.9": ["overboost"], "9.7 9.3 1.7": ["nonoperational"], "1.2 8.7 3.0": ["penalites"], "10.7 -5.9 3.6": ["eaga"], "18.2 0.9 -6.0": ["ithas"], "7.8 4.7 10.5": ["cementation"], "5.3 6.5 12.2": ["jumpout"], "-10.9 5.8 11.4": ["speedwork"], "17.6 13.9 6.7": ["mineshafts"], "6.1 9.1 7.8": ["ngoni"], "9.4 -2.1 20.1": ["ava"], "17.7 -0.9 6.5": ["haus"], "7.9 8.2 2.4": ["pectore"], "24.2 8.4 14.5": ["yuppy"], "5.5 23.1 9.7": ["agonistic"], "10.9 12.8 11.5": ["fitch"], "8.1 4.2 13.0": ["kantha"], "21.7 7.5 10.3": ["tetrahedron"], "2.1 12.0 3.3": ["palaeochannel"], "10.4 -1.4 7.9": ["processionals"], "7.1 4.6 25.9": ["pupus"], "1.5 5.9 24.5": ["husked"], "11.3 13.2 8.1": ["disinterestedly"], "11.9 5.9 30.5": ["cheeseboard"], "-2.6 19.1 8.0": ["flukish"], "5.5 12.6 9.9": ["istic"], "-3.1 9.3 8.7": ["genderqueer"], "15.0 12.8 8.7": ["timewasting"], "17.0 8.7 28.9": ["woodie"], "-11.2 9.7 -3.3": ["fibrinolytic"], "6.0 4.0 4.4": ["teletypes"], "1.7 11.2 14.7": ["wigan"], "8.2 -2.5 2.2": ["destra"], "4.4 19.0 4.6": ["guruji"], "0.8 13.1 10.1": ["resourses"], "2.7 24.8 17.4": ["chokeholds"], "12.4 15.3 9.6": ["unseriousness"], "19.5 5.9 23.4": ["playdough"], "5.4 11.5 7.5": ["entrustment"], "14.7 10.6 7.0": ["whoso"], "22.1 16.5 9.4": ["everpresent"], "-0.7 24.7 -1.8": ["coopt"], "6.6 11.4 11.5": ["wonkery"], "9.7 12.8 6.8": ["sheerly"], "-2.8 7.5 -5.8": ["workstreams"], "5.4 12.6 11.1": ["carryons"], "0.0 -0.2 10.1": ["candlelighting"], "3.8 1.5 -5.1": ["neurostimulators"], "14.3 10.2 30.0": ["cotoneaster"], "4.7 31.1 3.4": ["reconquered"], "1.5 10.1 8.7": ["stablemaster"], "24.2 21.3 14.9": ["enormousness"], "4.4 19.5 9.2": ["idealogical"], "10.7 -2.2 18.6": ["kente"], "2.9 10.9 7.7": ["firmwares"], "5.9 15.1 6.2": ["uncontacted"], "5.3 9.6 3.8": ["becuz"], "7.2 9.9 9.5": ["vant"], "6.0 13.0 12.6": ["kaun"], "20.3 8.9 17.0": ["fakey"], "8.7 18.8 10.0": ["loverboy"], "4.0 9.0 11.9": ["rightcenter"], "-0.7 7.1 2.9": ["miscible"], "12.2 12.6 10.6": ["prole"], "5.9 4.3 17.1": ["pada"], "11.6 14.2 19.8": ["sneezy"], "8.5 9.5 14.8": ["grubbed"], "-6.5 -1.8 10.2": ["meed"], "0.8 9.0 3.7": ["barebacking"], "9.5 14.0 8.8": ["evah"], "17.0 17.6 9.0": ["bluescreen"], "5.2 11.0 6.7": ["listenin"], "6.8 4.3 4.2": ["raincheck"], "4.8 -2.9 11.2": ["dehorning"], "6.4 14.5 1.9": ["ungated"], "8.2 10.6 9.3": ["cliffhanging"], "-3.0 3.0 6.8": ["desaturation"], "5.1 15.1 -3.9": ["instillations"], "4.4 12.7 19.9": ["blistery"], "1.9 10.2 6.9": ["kinescopes"], "0.7 4.1 12.1": ["supernatant"], "12.7 6.7 8.7": ["chanteuses"], "4.0 12.9 4.9": ["derivatively"], "2.2 26.1 3.1": ["anticommunism"], "5.2 12.2 15.3": ["showtune"], "9.1 18.4 10.5": ["dashingly"], "5.8 6.7 11.3": ["gloria"], "11.7 15.7 12.8": ["nimby"], "5.4 16.9 4.1": ["outloud"], "7.6 10.9 1.8": ["unidentifed"], "22.1 6.4 14.3": ["polychromatic"], "-2.7 1.1 -0.4": ["haemostasis"], "10.0 14.4 9.1": ["flameless"], "4.7 0.2 -3.6": ["wesbite"], "10.5 8.0 -4.0": ["etyres"], "2.0 5.3 15.9": ["beaders"], "-4.0 2.2 5.1": ["potentiates"], "3.1 6.1 16.3": ["kyo"], "-6.1 -1.2 5.2": ["nonminority"], "7.4 14.5 9.6": ["unsentimentally"], "9.9 11.3 1.9": ["polycentric"], "10.4 10.2 6.1": ["screencaps"], "2.8 12.4 16.9": ["antifouling"], "3.1 -0.8 7.6": ["spottiness"], "10.5 10.7 9.3": ["recombines"], "-2.3 13.3 -3.8": ["shahada"], "1.0 5.0 18.2": ["canadensis"], "7.7 4.6 6.6": ["standstills"], "13.3 17.9 10.4": ["scrublands"], "9.6 19.9 13.4": ["federer"], "-0.1 7.3 7.6": ["stepgrandfather"], "7.5 16.6 14.3": ["majesties"], "4.5 10.0 13.5": ["oughts"], "10.8 -4.5 2.8": ["orderd"], "58.7 6.9 8.0": ["gaint"], "2.4 5.7 11.4": ["worka"], "3.2 12.1 12.1": ["choreographically"], "9.3 16.9 30.4": ["woodcocks"], "8.5 17.6 4.1": ["incompetant"], "11.1 35.5 12.8": ["corsairs"], "4.8 12.6 27.6": ["juleps"], "-6.6 -2.1 8.7": ["geog"], "-7.6 7.1 5.7": ["fairests"], "-0.7 5.6 4.8": ["stakeswinner"], "9.7 24.0 13.7": ["doest"], "14.8 5.4 20.5": ["kiva"], "-0.3 5.0 5.4": ["parturition"], "16.1 4.8 24.8": ["sugarplum"], "6.4 1.5 22.8": ["shrieky"], "-1.6 0.2 5.5": ["subdivison"], "4.2 20.7 12.6": ["supect"], "7.3 16.7 -0.0": ["himslef"], "5.7 18.0 3.5": ["boorishly"], "3.3 15.6 12.8": ["stickside"], "12.1 6.7 7.0": ["eller"], "4.8 4.7 3.0": ["cantera"], "5.9 14.1 8.9": ["paternally"], "8.1 -2.6 5.4": ["fluorochemicals"], "5.8 14.5 6.5": ["docilely"], "7.6 10.2 13.9": ["preggo"], "10.8 -2.1 2.9": ["thisweek"], "-2.0 10.1 -3.6": ["mitigator"], "11.9 10.7 13.8": ["footwells"], "12.3 27.0 23.3": ["quarterdeck"], "6.5 8.1 15.3": ["shrubland"], "8.4 15.5 11.2": ["sidearmed"], "-3.9 7.3 6.6": ["depletable"], "5.9 11.0 22.0": ["ickiness"], "6.3 10.7 2.4": ["sexcapade"], "-1.5 13.0 11.2": ["mourinho"], "8.4 12.2 19.0": ["bokeh"], "8.1 14.4 4.8": ["reagan"], "14.8 30.5 10.1": ["hegemonism"], "-0.2 0.7 1.3": ["gearmotors"], "19.4 10.0 17.1": ["sega"], "-5.1 6.9 6.7": ["interpellations"], "10.4 -3.1 13.3": ["muli"], "4.7 23.1 18.4": ["sunniness"], "7.1 7.5 3.9": ["notetaking"], "7.4 12.4 3.7": ["objectifies"], "10.0 -1.2 14.6": ["boxercise"], "4.0 8.4 14.4": ["selena"], "17.0 -2.3 9.4": ["stripteases"], "-0.8 16.3 19.6": ["photoperiod"], "-9.8 -1.0 5.3": ["apportionments"], "10.0 -0.9 7.9": ["webconferencing"], "-2.5 29.2 7.6": ["fightings"], "5.8 10.6 11.4": ["alonso"], "6.3 9.8 23.8": ["endemics"], "4.6 8.8 -0.0": ["paystubs"], "-11.5 11.2 13.2": ["unallot"], "-3.6 6.0 3.9": ["leukaemias"], "5.9 21.0 10.9": ["injudiciously"], "2.7 14.1 17.1": ["plowers"], "9.5 5.3 7.1": ["indefinately"], "5.0 14.3 12.4": ["barnes"], "1.5 5.8 3.0": ["donationware"], "14.1 6.2 -2.9": ["quitely"], "7.1 3.6 10.0": ["cementitious"], "9.3 12.7 13.7": ["desirables"], "8.7 17.7 10.7": ["fecking"], "2.2 7.5 11.1": ["pianissimos"], "21.2 10.5 13.5": ["shotgunned"], "-3.4 -1.3 6.1": ["regental"], "11.5 18.5 9.3": ["bejabbers"], "5.4 9.2 18.5": ["calliper"], "4.7 8.3 -4.4": ["realease"], "19.1 11.3 6.7": ["commodifying"], "14.3 8.9 17.1": ["mongoloid", "richt"], "16.3 18.0 12.6": ["flytippers"], "8.4 -2.3 10.1": ["erectors"], "11.0 5.0 -0.8": ["openning"], "2.9 21.3 12.2": ["estranging"], "7.6 4.5 13.7": ["runups"], "-12.6 13.8 5.5": ["shidduch"], "15.4 7.7 29.5": ["beetroots"], "12.2 11.9 16.0": ["sprogs"], "-1.9 8.2 7.6": ["emerg"], "11.2 -0.9 -4.8": ["multimarket"], "3.6 11.0 3.4": ["intented"], "2.8 6.2 12.3": ["artiness"], "0.5 -0.5 6.5": ["equestrienne"], "1.0 19.1 10.0": ["dialouge"], "5.5 6.8 21.6": ["grayest"], "13.9 4.5 4.2": ["bankrupty"], "9.5 -2.0 8.0": ["reclaimer"], "5.6 11.1 21.4": ["kha"], "-3.0 10.0 17.4": ["gyud"], "11.0 -3.9 16.7": ["pearlized"], "1.2 10.2 6.5": ["sportmanship"], "12.9 4.9 3.1": ["carrels"], "8.5 -3.2 -1.5": ["nouveaux"], "7.9 21.9 30.3": ["shrikes"], "2.9 -4.4 1.9": ["ational"], "0.4 7.7 7.1": ["anomoly", "mier"], "13.9 11.8 19.9": ["moistens"], "7.2 16.9 5.7": ["wastegate"], "29.8 24.8 18.2": ["minotaurs"], "17.3 10.9 13.9": ["errrr"], "7.4 8.3 11.2": ["isp"], "8.8 4.1 10.6": ["tilma"], "5.8 14.4 3.9": ["generousity"], "10.3 19.4 8.5": ["runic"], "10.4 3.7 23.8": ["husking"], "19.9 7.3 12.0": ["tragics"], "6.2 18.5 7.4": ["riboswitches"], "7.1 5.8 10.7": ["filmstrips"], "4.4 11.0 6.2": ["accomodative"], "8.0 23.7 21.1": ["cambium"], "3.0 13.8 14.6": ["aight"], "13.0 10.4 12.0": ["tsk"], "8.1 4.9 8.5": ["vorapaxar"], "11.6 6.4 34.4": ["edibility"], "-1.6 8.7 5.4": ["devolvement"], "7.0 4.9 -1.8": ["warrantied"], "0.1 7.5 18.9": ["saponins"], "11.3 21.1 15.8": ["impiety"], "-0.4 5.8 23.8": ["saiga"], "15.5 8.3 7.6": ["autostereoscopic"], "16.3 3.3 31.0": ["chards"], "13.1 -3.6 36.4": ["bucatini"], "14.0 13.6 18.1": ["snapmare"], "-0.9 14.0 12.4": ["kol"], "-5.6 2.2 1.6": ["agranulocytosis"], "13.3 -0.1 33.3": ["brandied"], "-1.9 14.2 15.7": ["knowed"], "8.7 3.9 9.4": ["hotlinks"], "17.7 9.5 14.1": ["babushkas"], "-0.3 7.7 12.8": ["shamba"], "4.3 21.2 8.1": ["srilanka"], "-6.8 8.1 5.9": ["residuary"], "-2.8 4.7 -1.8": ["explicity"], "3.7 11.2 5.8": ["selbst"], "13.4 13.6 16.6": ["minging"], "4.3 -2.4 15.1": ["outros"], "2.4 6.7 9.3": ["intravitreal"], "13.3 15.3 26.1": ["rasher"], "7.2 16.1 8.8": ["personna"], "6.0 19.5 9.6": ["numerously"], "0.1 7.5 9.6": ["gruppo"], "1.1 10.4 2.5": ["nitric"], "6.9 31.2 6.9": ["napalmed"], "15.6 6.2 9.0": ["taiwan"], "9.1 14.0 0.5": ["deadend"], "14.7 13.5 17.0": ["handjob"], "-0.1 2.4 5.3": ["catergory"], "5.9 14.7 16.1": ["conservationism"], "8.8 7.6 10.0": ["notchback"], "12.8 4.8 17.9": ["watermill"], "5.1 -9.9 4.9": ["kur"], "3.1 8.6 9.6": ["ultrapure"], "-1.1 5.9 5.7": ["concubinage"], "0.0 6.9 7.6": ["parainfluenza"], "-1.6 15.1 6.4": ["posseses"], "0.9 19.5 3.3": ["intellegent"], "6.6 9.8 5.9": ["filmakers"], "10.4 11.3 11.2": ["postwoman"], "4.4 16.5 2.4": ["strengh"], "-2.8 -1.8 -15.6": ["inhis"], "8.1 -3.4 10.5": ["campdraft"], "0.1 2.2 8.9": ["reinterment"], "9.3 1.9 -6.2": ["commisioned"], "1.1 9.1 7.1": ["codependence"], "4.5 -7.4 9.0": ["xtra"], "8.9 12.8 6.4": ["somes"], "4.8 7.9 21.3": ["nutraloaf"], "4.4 7.3 9.5": ["accoustic"], "8.7 18.1 16.8": ["inswingers"], "7.0 4.3 41.0": ["killifish"], "10.5 8.9 7.5": ["zimbabwe"], "9.6 16.0 10.0": ["highlander"], "3.4 8.1 22.4": ["chalcedony"], "8.1 14.9 10.3": ["inadvertant"], "4.4 9.3 4.5": ["investement"], "-3.1 10.0 6.7": ["ratifiers"], "-3.0 11.5 18.3": ["multicab"], "7.0 15.0 5.1": ["denotation"], "7.1 12.9 6.1": ["laserlike"], "13.4 0.2 2.4": ["parleyed"], "22.3 22.2 19.5": ["fauns"], "3.5 6.7 10.9": ["unsterile", "trichloroanisole"], "21.0 0.4 42.5": ["cray"], "2.4 -1.1 7.1": ["depilatories"], "5.9 -0.6 -3.1": ["novated"], "-8.4 7.4 -1.0": ["uptil"], "2.7 12.1 14.9": ["denudation", "homless"], "12.8 21.1 8.6": ["hades"], "5.6 4.4 6.9": ["rescreen"], "5.1 9.5 10.2": ["milatuzumab"], "5.1 -3.6 3.7": ["beforethe"], "-2.3 6.7 10.7": ["raod"], "20.2 19.4 -1.4": ["uncloaked"], "3.9 1.4 5.5": ["plusieurs"], "0.0 -1.7 1.1": ["hfa"], "1.7 13.3 2.5": ["ostracization"], "-1.2 6.5 9.8": ["operagoers"], "19.7 9.1 11.5": ["preverbal"], "10.6 5.7 5.3": ["usualy"], "1.9 2.3 8.5": ["refiguring"], "12.9 13.9 16.7": ["nighty"], "-0.4 19.7 15.7": ["colorum"], "5.8 2.2 4.3": ["uncollateralized"], "9.5 5.5 20.9": ["unwrinkled"], "2.4 12.2 8.2": ["jodis"], "10.6 1.9 16.5": ["belltower"], "7.5 9.7 14.0": ["contigency"], "0.3 5.3 22.8": ["meen"], "-9.4 9.2 8.6": ["dermatomyositis"], "3.6 1.9 5.1": ["yakked"], "0.8 15.8 7.4": ["shabbos"], "11.7 13.6 18.6": ["cyprus"], "1.3 21.0 9.7": ["callowness"], "3.4 -4.7 5.6": ["egovernment"], "13.7 8.6 8.9": ["eden"], "4.9 7.9 3.0": ["phosphoric"], "3.0 10.0 2.1": ["backgrounded"], "7.4 3.0 1.8": ["manditory"], "10.5 8.8 4.2": ["nsa"], "4.7 18.2 10.7": ["unassailably"], "1.4 10.3 6.4": ["biocidal"], "5.3 23.0 7.1": ["transhumanists"], "-5.3 8.5 35.0": ["steelheading"], "12.2 3.0 7.3": ["shoutcast"], "2.5 14.2 19.2": ["hangtime"], "30.2 16.8 15.1": ["colosseum"], "-8.3 7.5 0.0": ["reemploy"], "16.1 18.6 11.1": ["prats"], "4.1 15.7 7.0": ["rightwards"], "13.9 3.9 -6.2": ["inits"], "15.1 9.2 30.4": ["saltbush"], "1.6 8.0 7.8": ["pareve"], "7.1 15.6 18.9": ["yack"], "5.6 9.5 1.3": ["cabriolets"], "11.0 6.4 10.9": ["howbeit"], "6.7 3.8 4.1": ["cul"], "16.4 1.9 10.5": ["stockbrokerage"], "2.9 17.1 12.4": ["shotblocking"], "-4.3 5.1 8.6": ["polyamines"], "3.2 12.8 15.3": ["hangnails"], "4.3 2.3 25.2": ["galettes"], "-1.5 8.9 10.1": ["karateka"], "-4.4 8.1 1.7": ["trabeculectomy"], "3.3 8.5 10.2": ["vismodegib"], "5.8 7.1 14.8": ["outsoles"], "16.8 17.3 22.5": ["chytridiomycosis"], "4.9 16.1 18.5": ["parasitized"], "-1.4 2.6 8.8": ["relet"], "-2.2 -0.9 5.5": ["monde"], "6.2 18.1 38.3": ["tidepools"], "3.4 13.8 5.7": ["profoundness"], "0.3 7.0 1.7": ["intranasally"], "-1.1 22.3 2.1": ["marjaiyah"], "19.6 11.6 7.3": ["backlighted"], "-0.0 6.6 5.5": ["multitenancy"], "-2.8 5.5 9.9": ["cand"], "13.7 11.1 5.6": ["gajillion"], "7.5 9.6 20.8": ["tarn"], "7.6 17.0 11.9": ["diffusely"], "7.6 8.9 9.0": ["bentley"], "3.5 4.7 6.9": ["securitizer"], "2.3 12.2 9.1": ["lekin"], "2.1 21.3 1.8": ["monotheist"], "6.2 18.7 7.1": ["churlishness"], "-0.8 -5.9 -0.1": ["submited"], "6.8 10.4 16.5": ["officinalis"], "-4.7 1.8 4.4": ["answersheets"], "1.0 11.0 -1.1": ["thatthey"], "7.2 10.7 3.0": ["guntas"], "3.6 1.7 19.7": ["chon"], "-1.5 32.6 12.3": ["cooldowns"], "4.7 -1.1 4.5": ["tartrate"], "9.2 21.7 9.5": ["cannnot"], "18.1 5.4 7.2": ["gaz"], "9.3 13.5 16.4": ["unbought"], "-4.6 4.5 6.0": ["plasmin"], "8.3 5.1 10.7": ["utils"], "4.8 1.6 21.7": ["underlayer"], "9.9 4.5 14.2": ["holmes"], "7.8 10.5 12.6": ["arpeggiated"], "9.6 7.0 14.1": ["tremolite"], "2.1 7.5 9.0": ["navicular"], "0.9 12.1 17.8": ["endophyte"], "4.5 9.5 6.1": ["gasifying"], "5.7 15.1 13.5": ["midgut"], "-1.5 15.2 7.9": ["psychophysical"], "5.9 14.4 14.2": ["overcall"], "-7.0 8.2 13.0": ["nangyari"], "16.2 7.3 11.1": ["collosal"], "2.6 4.7 8.9": ["chondromalacia"], "13.9 13.7 27.2": ["promontories"], "7.7 20.7 7.5": ["cockiest"], "1.2 4.3 10.7": ["semidetached"], "6.8 8.4 2.0": ["acused"], "11.9 10.5 19.1": ["barnyards"], "4.6 8.6 8.4": ["subparallel"], "12.0 14.4 13.6": ["toughman"], "-0.3 8.0 6.1": ["percutaneously"], "10.8 0.3 14.4": ["proinsulin"], "-6.2 3.4 0.6": ["consective"], "8.8 9.7 10.5": ["boppy"], "3.1 8.9 15.1": ["quan"], "3.9 12.8 12.9": ["bowdlerized"], "3.5 -1.8 3.8": ["hosp"], "13.2 11.3 15.8": ["upthrust"], "4.2 6.4 41.4": ["piccata"], "4.0 13.8 15.7": ["looniest"], "11.3 10.7 5.6": ["zettabytes"], "-2.3 7.8 5.1": ["hillwalkers"], "0.7 -3.2 13.9": ["shavees"], "2.4 -0.9 11.0": ["paks"], "16.0 8.0 4.7": ["zal"], "12.8 13.8 19.2": ["everythings"], "15.4 1.1 6.7": ["dowload"], "9.0 16.6 15.3": ["micrometeorite"], "1.2 13.5 -1.4": ["perservered"], "4.0 10.6 8.0": ["combinational"], "11.9 8.7 12.4": ["undersells"], "17.2 0.9 0.9": ["dabblings"], "-4.0 1.5 8.9": ["bh"], "12.6 1.7 -13.6": ["formely"], "8.2 5.9 16.7": ["bunko"], "0.8 12.7 15.1": ["exudate"], "-1.4 0.2 16.9": ["fisrt"], "-2.7 12.5 4.0": ["elicitation"], "4.0 9.6 4.6": ["borescope"], "1.0 7.3 -1.1": ["ionizers"], "11.9 14.4 5.3": ["cought"], "9.5 6.5 28.6": ["adze"], "11.3 5.3 22.2": ["marula"], "5.0 2.7 12.3": ["conventioneer"], "6.6 0.4 6.8": ["gane"], "16.9 3.8 4.6": ["collaboratory"], "3.1 -0.1 15.7": ["sobrang"], "4.8 12.9 10.8": ["obv"], "-2.2 5.8 -2.7": ["derecognized"], "9.5 5.4 11.7": ["displ"], "10.9 12.8 4.2": ["refold"], "4.9 8.9 0.1": ["diopters"], "11.9 14.5 14.9": ["micrometeoroid", "dood"], "-2.5 7.1 14.2": ["tillering"], "8.3 22.1 4.4": ["satanists"], "20.4 20.5 16.1": ["yawing"], "5.4 20.4 7.6": ["antiparticles"], "0.8 14.2 10.2": ["anthropologically"], "8.0 11.1 2.6": ["decaled"], "-2.8 16.3 3.8": ["meningococcus"], "7.6 2.9 15.4": ["emptyhanded"], "18.3 4.3 9.0": ["brainchildren"], "23.4 7.9 19.3": ["stinkiest"], "2.4 8.6 10.9": ["occlusive"], "3.4 9.7 11.2": ["bettter"], "3.7 5.8 9.3": ["osr"], "24.2 0.4 7.1": ["smoothe"], "2.7 12.1 15.1": ["overspreading"], "-1.0 10.5 0.4": ["qazis"], "10.6 11.2 4.0": ["conjugating"], "8.0 12.6 5.2": ["controllably"], "0.9 10.6 7.8": ["bugfix"], "10.5 12.3 17.6": ["gib"], "11.0 23.6 19.6": ["disorients"], "18.4 16.3 17.7": ["piteously"], "3.3 6.3 18.4": ["ethnobotanist"], "-1.4 9.5 15.2": ["mortem"], "17.2 2.4 11.3": ["matcher"], "-4.3 10.7 7.9": ["ihram"], "-3.4 21.5 1.4": ["secessions"], "4.7 -1.2 9.5": ["capless"], "2.5 9.3 5.5": ["neorealist"], "4.7 9.6 13.6": ["zonation"], "7.3 5.7 6.5": ["nanorod"], "-1.8 6.7 5.8": ["deferent"], "18.6 17.8 25.1": ["woodworm"], "3.5 7.7 11.1": ["vastu"], "3.4 6.9 18.7": ["tenon"], "-0.3 2.7 11.4": ["chansons"], "5.5 19.2 30.3": ["cottonmouths"], "-3.5 13.2 10.3": ["romanticization"], "11.6 6.6 8.3": ["proportioning"], "9.1 2.3 8.7": ["bioinformaticians"], "13.4 8.1 26.8": ["whippoorwill"], "-11.4 5.7 3.3": ["nephrotoxicity"], "3.7 10.5 7.8": ["aobut"], "24.7 18.5 24.9": ["wormlike"], "6.2 15.6 3.9": ["uncoerced"], "6.4 4.1 32.5": ["endives"], "8.6 -9.7 6.3": ["discoverd"], "-0.3 8.8 4.9": ["crowdedness"], "4.6 0.2 6.0": ["dalasi"], "5.1 -3.3 9.9": ["spikier"], "15.6 18.6 11.6": ["engineless"], "10.3 2.3 25.5": ["rubberwood"], "20.3 11.3 12.2": ["mussing"], "-4.3 -3.3 0.8": ["plasticisers"], "9.5 3.2 18.4": ["dehydrators"], "5.4 8.0 7.2": ["methenolone"], "16.3 23.5 13.1": ["noogie"], "5.4 5.8 -1.1": ["vlingo"], "-4.1 31.4 12.4": ["ordnances"], "8.0 -6.8 20.5": ["playsuits"], "-5.6 10.1 -2.0": ["ableto"], "-3.3 1.1 7.5": ["cif"], "0.8 5.3 12.2": ["erythrocyte"], "5.0 10.9 9.2": ["nanodots"], "1.8 12.3 17.5": ["zhi"], "14.5 4.9 19.1": ["abbatoir"], "8.1 18.4 30.1": ["tahrs"], "20.3 13.5 18.1": ["dufus"], "8.3 5.7 13.2": ["pentlandite"], "6.5 4.8 9.7": ["refractor"], "12.4 10.8 -3.6": ["builtin"], "5.3 -5.0 -9.3": ["chaiman"], "9.8 1.3 4.2": ["miniskirted"], "10.1 14.1 16.3": ["babblers"], "4.0 15.2 -0.0": ["symbolisms"], "12.9 7.4 26.3": ["harlequins"], "7.0 5.5 14.4": ["handbuilt"], "-3.7 -2.2 16.8": ["alb"], "-0.1 4.0 5.6": ["tradespersons"], "2.6 15.3 7.9": ["cowboying"], "6.7 3.1 14.0": ["recipies"], "9.2 1.6 7.4": ["fineries"], "4.7 12.6 11.5": ["uncategorizable"], "15.1 9.3 5.5": ["salaciously"], "7.7 6.2 0.0": ["fixtured"], "4.6 4.6 12.3": ["rasikas"], "9.7 18.1 7.6": ["ruffing"], "4.8 7.1 -1.2": ["againstthe"], "13.0 12.3 22.1": ["bisons"], "1.3 10.0 8.4": ["autosomal"], "3.7 18.7 7.8": ["mutagens"], "8.5 7.0 0.7": ["hometeam"], "18.5 5.2 15.1": ["poobah"], "2.4 13.0 14.7": ["hyperextend"], "6.0 5.2 14.0": ["continua"], "18.0 17.1 7.4": ["conjurers"], "-3.2 26.3 10.1": ["jumpmaster"], "6.8 13.4 -1.4": ["tantamounts"], "6.6 6.9 29.8": ["phalaenopsis"], "9.6 8.0 6.5": ["mangas"], "5.0 1.6 4.8": ["tejano"], "1.9 5.2 -2.0": ["oficials"], "7.6 10.7 23.3": ["multibeam"], "5.5 3.2 13.6": ["redeposited"], "6.4 4.8 5.3": ["bookstands"], "6.1 26.4 12.4": ["dwelleth"], "11.5 14.2 13.1": ["biffo"], "12.2 20.5 22.1": ["nunchuks"], "14.5 18.4 14.1": ["covens"], "8.2 3.3 25.5": ["epazote"], "4.8 16.6 14.2": ["filthiness"], "-1.4 23.0 6.7": ["objectivist"], "-4.0 10.6 6.9": ["shouldbe"], "-6.4 0.2 14.2": ["nonimmigrants"], "4.3 2.2 6.7": ["licencia"], "14.3 13.0 3.5": ["semiliterate"], "15.5 22.0 20.4": ["whatchamacallit"], "8.4 18.7 10.9": ["waring"], "13.6 18.6 21.8": ["whetstone"], "12.5 12.1 29.4": ["croton"], "4.0 8.5 24.1": ["nui"], "4.5 5.6 11.5": ["underfollowed"], "5.6 4.7 0.0": ["andhe"], "15.4 1.4 7.8": ["crystalise"], "-12.0 3.3 2.0": ["cooperativeness"], "3.2 7.9 0.1": ["revaluating"], "-5.8 8.8 7.2": ["fascial"], "12.9 3.0 34.0": ["potatos"], "7.6 13.2 5.1": ["comicbooks"], "-6.8 11.0 7.6": ["fullfil"], "4.2 7.3 2.6": ["contro"], "6.4 12.5 24.4": ["chiru"], "3.0 16.3 11.9": ["manful"], "6.4 10.7 13.5": ["schoolmistress"], "18.2 7.9 22.6": ["jagging"], "2.4 5.3 16.4": ["lave"], "-3.3 -4.1 0.4": ["coowner"], "13.4 12.2 12.9": ["limescale"], "8.1 8.7 8.9": ["deconvolution"], "-1.9 17.9 5.0": ["stigmatism"], "15.0 17.8 12.8": ["berk"], "8.9 1.1 -1.2": ["convenants"], "-3.4 -1.3 19.0": ["yardings"], "16.0 13.2 1.8": ["hiptop"], "14.4 7.3 -0.8": ["launderer"], "7.6 -3.9 11.4": ["nies"], "7.6 14.1 20.1": ["streambanks"], "3.4 -3.3 9.1": ["recepients"], "5.5 11.9 9.8": ["freerunning"], "4.7 8.6 4.2": ["beyong"], "13.0 16.0 16.1": ["aerates"], "-6.6 16.4 6.6": ["halakha"], "11.8 22.9 23.6": ["yardarm"], "4.8 5.2 17.1": ["conservational"], "2.1 1.8 2.7": ["laywoman"], "-5.7 -0.7 3.2": ["teleconferenced"], "15.3 15.7 6.0": ["twitting"], "-3.5 7.9 5.1": ["epistaxis"], "5.6 1.2 15.1": ["synephrine"], "1.8 9.7 14.5": ["sya"], "-4.2 8.1 4.3": ["altough"], "15.2 10.5 12.9": ["hairiness"], "26.4 5.5 6.4": ["flatpack"], "6.7 1.6 14.9": ["fragrantly"], "1.4 20.1 -0.4": ["bayat"], "12.8 14.9 4.8": ["multireligious"], "12.1 17.8 10.5": ["ragamuffins"], "-0.6 -1.2 4.3": ["eariler"], "13.1 14.2 11.8": ["pedlar"], "24.4 1.0 10.7": ["rollerball"], "6.1 8.6 14.8": ["bittersweetness"], "4.0 2.1 7.6": ["awd"], "4.1 18.6 0.2": ["sequal"], "13.4 10.9 19.1": ["calyx"], "3.7 0.8 2.0": ["currenlty"], "4.5 1.4 9.5": ["rfid"], "16.4 12.0 4.9": ["unreeled"], "7.5 15.8 8.5": ["managerialism"], "7.9 5.5 16.7": ["dyestuff"], "-1.2 6.6 5.2": ["nondisruptive"], "-1.2 7.4 16.6": ["phencyclidine"], "14.5 7.8 12.8": ["salesgirls"], "-3.6 6.9 6.8": ["immunoreactivity"], "-13.3 14.7 8.0": ["misremember"], "0.9 4.8 1.6": ["underrecognized"], "13.5 15.9 10.0": ["ornithopter"], "8.1 3.4 0.1": ["photofinishers"], "-1.8 8.0 18.5": ["mushier"], "13.4 6.8 24.5": ["bichon"], "11.4 2.7 17.6": ["wight"], "19.8 19.2 9.8": ["poseable"], "5.1 5.9 8.9": ["resumptions"], "6.2 7.9 26.3": ["glassful"], "17.7 18.7 17.3": ["superstorm"], "1.8 9.3 4.1": ["keyholder"], "6.5 3.8 16.1": ["hotlink"], "-3.8 15.1 4.2": ["intermediating"], "-13.2 7.6 4.6": ["vulvodynia"], "14.8 14.1 4.5": ["crassest"], "8.9 4.9 24.6": ["moscato"], "-3.0 23.3 4.7": ["noncommunist"], "0.4 10.3 5.3": ["tain"], "20.4 -4.3 2.9": ["stodgier"], "6.0 5.6 -0.7": ["bemuses"], "16.8 17.3 5.6": ["virtuality"], "10.2 -1.8 9.3": ["fut"], "-5.0 20.4 6.1": ["idealise"], "7.8 2.3 0.1": ["dernier"], "9.7 4.1 3.8": ["hifi"], "-5.2 6.4 0.9": ["preamplifiers", "constitutent"], "10.4 15.0 13.0": ["snivel"], "7.5 -4.6 8.8": ["metallised"], "6.1 19.6 9.1": ["delusionally"], "3.2 15.1 7.6": ["indebting"], "5.8 9.0 34.6": ["applewood"], "16.7 14.1 20.7": ["cavelike"], "-1.2 6.0 5.5": ["genericization"], "-2.2 7.8 13.1": ["windspeeds"], "15.4 26.0 2.0": ["counterpoise"], "13.6 7.2 4.8": ["sightscreens"], "15.7 15.4 13.9": ["profligately"], "5.1 9.5 3.8": ["anniv"], "5.9 9.6 2.4": ["contraints"], "-6.9 27.1 -3.1": ["antinational"], "12.7 17.0 35.2": ["weka"], "17.2 15.4 18.7": ["gummint"], "5.2 11.1 13.8": ["biodegraded"], "-0.3 9.4 9.0": ["hygeine"], "0.3 -0.8 8.6": ["nitong"], "6.0 18.1 4.9": ["commotions"], "6.7 16.8 8.8": ["nonmaterial"], "9.5 14.8 2.0": ["discriminatorily"], "10.1 3.6 15.6": ["giddier"], "2.5 -1.4 8.1": ["partido"], "4.4 5.1 12.3": ["piggybanks"], "5.3 3.7 22.6": ["stubbles"], "4.5 1.3 3.3": ["reinitiating"], "1.1 6.1 6.4": ["annotates"], "0.8 1.0 9.3": ["beom"], "5.6 12.3 6.4": ["aving"], "-5.9 2.8 8.3": ["macrovascular"], "7.2 19.9 13.5": ["plasmodium"], "12.4 7.8 5.3": ["cadging"], "3.5 -4.2 4.3": ["debottleneck"], "6.3 8.3 4.9": ["cinemascope"], "1.2 12.0 6.3": ["infelicitous"], "2.0 2.7 9.9": ["reopener"], "6.2 7.9 10.0": ["yucking"], "12.3 5.1 13.8": ["springiness"], "7.3 -4.9 16.2": ["hectolitre"], "15.0 7.1 3.7": ["doodlers"], "-3.8 1.8 12.5": ["meyer"], "18.0 -4.0 2.4": ["kiboshed"], "5.2 2.3 5.6": ["namechecks"], "3.9 12.8 9.7": ["unvoiced"], "17.0 13.0 5.6": ["vapourware"], "0.5 -2.1 0.4": ["disallowances"], "-7.9 13.0 3.6": ["penciler"], "-4.3 7.9 9.6": ["compartmental"], "14.5 6.1 10.1": ["steepled"], "-0.5 3.0 2.1": ["misadministration"], "3.0 9.8 13.5": ["hongi"], "7.3 2.1 7.9": ["crystalised"], "4.6 10.7 29.3": ["tablemate"], "7.1 -2.4 3.6": ["unos"], "1.0 8.6 13.1": ["pyrosequencing"], "-2.1 8.3 -0.6": ["nikaah"], "4.9 5.4 -2.1": ["alread"], "2.4 10.3 16.5": ["offday"], "14.1 13.8 7.7": ["amsazing"], "13.1 2.1 18.4": ["servals"], "7.1 -1.2 12.6": ["smoothy"], "5.0 7.9 1.4": ["overdues"], "10.9 21.9 8.4": ["postracial"], "23.7 21.7 8.5": ["antitakeover"], "13.1 6.0 14.1": ["ofrenda"], "14.3 16.3 13.1": ["pharoah"], "7.5 5.6 3.1": ["smartboards"], "18.9 8.0 14.6": ["weatherbeaten"], "11.4 -4.2 5.8": ["microfabricated"], "15.7 11.9 38.5": ["trotline"], "20.7 29.3 11.0": ["vanquisher"], "-1.0 8.2 5.4": ["overperformed"], "12.4 16.0 10.0": ["kinect"], "8.2 -1.2 12.3": ["sudser"], "5.4 4.4 11.7": ["refired"], "-4.9 6.6 4.5": ["aout"], "2.5 9.2 8.4": ["vocalising"], "0.0 6.7 2.2": ["divx"], "2.9 -2.4 1.7": ["cz"], "2.7 10.2 13.4": ["woodburner"], "4.3 15.2 8.4": ["gooner"], "5.7 2.4 11.6": ["dsp"], "-3.8 11.5 2.8": ["recomplete"], "5.5 8.1 14.1": ["stepback"], "10.1 16.1 29.6": ["sampans"], "-2.1 3.7 14.0": ["ceramides"], "7.6 15.6 10.8": ["dourness"], "15.3 11.5 23.1": ["overstuff"], "8.4 19.8 8.7": ["lamed"], "-7.6 2.4 12.7": ["resurveyed"], "11.6 14.5 19.1": ["nock"], "14.5 12.2 23.0": ["gelignite"], "-0.0 7.6 9.4": ["gymming"], "1.7 9.1 4.7": ["decommitting"], "2.8 -1.6 2.0": ["representives"], "-6.6 9.8 12.5": ["polymyositis"], "4.7 1.0 2.3": ["ande"], "1.6 7.3 7.1": ["subheadline"], "11.0 16.4 1.5": ["exorcize"], "2.3 6.6 21.5": ["fleshier"], "4.3 27.7 4.4": ["dogfighter"], "7.9 1.8 9.2": ["durng"], "-0.9 4.0 3.0": ["poins"], "-3.8 0.2 9.6": ["solemnization"], "14.1 12.6 11.9": ["simper"], "1.9 22.4 11.0": ["clericalism"], "1.1 1.4 0.3": ["blogposts"], "10.5 6.0 26.4": ["annatto"], "7.5 9.1 4.1": ["undercapitalization"], "4.6 5.1 7.1": ["mmbbl"], "0.4 26.1 0.3": ["liberatory"], "-0.3 6.2 8.2": ["retroperitoneal"], "0.8 2.2 18.3": ["hapa"], "1.2 7.0 3.5": ["scada"], "10.7 10.5 8.8": ["ague"], "5.1 11.1 9.0": ["alphabetizing"], "4.3 2.3 14.4": ["aul"], "13.6 2.1 22.4": ["kolache"], "1.7 8.2 15.9": ["papain"], "1.0 2.2 7.3": ["hypoplasia"], "10.2 15.2 15.7": ["doomers"], "7.9 18.2 12.3": ["averageness"], "2.6 15.8 11.2": ["persuadables"], "10.2 14.7 23.1": ["potager"], "6.8 -1.7 16.3": ["monoprint"], "5.2 -4.3 8.8": ["preferrably"], "14.7 7.9 2.0": ["underinvesting"], "17.9 -1.6 8.0": ["zeitgeisty"], "4.8 10.3 2.2": ["counteraccusations"], "-4.7 7.9 5.5": ["carbidopa"], "1.7 3.1 6.7": ["underlyings"], "-6.4 1.2 14.8": ["watercolorists"], "14.1 6.9 3.8": ["tomographic"], "4.3 11.7 4.7": ["brooking"], "7.6 7.3 31.7": ["grosbeaks"], "-5.4 1.4 2.2": ["playe"], "9.1 1.9 -2.8": ["dropbox"], "14.5 12.0 27.8": ["mantas"], "6.9 4.0 8.1": ["cogitating"], "5.0 -1.8 14.2": ["rebecca"], "22.2 12.5 19.9": ["weightlessly"], "5.2 15.1 11.6": ["duende"], "5.6 8.2 -6.1": ["reemphasizes"], "-3.5 -3.9 14.7": ["hays"], "1.8 21.8 6.0": ["moslems"], "13.4 17.1 15.4": ["sleepin"], "5.4 23.6 11.5": ["hardcores"], "1.6 35.8 12.1": ["loadouts"], "7.6 2.0 3.0": ["isopropanol"], "13.6 4.5 13.8": ["naughties"], "-3.5 21.7 15.4": ["shew"], "7.1 -4.5 12.9": ["chay"], "9.5 -7.1 4.6": ["semiweekly"], "0.5 6.5 3.0": ["linac"], "7.5 16.7 8.4": ["preponderantly"], "3.7 5.0 -1.1": ["privvy"], "10.8 0.7 7.5": ["multisports"], "1.1 10.5 2.5": ["anemias"], "2.5 1.8 5.5": ["reskilling"], "4.9 10.8 -3.2": ["electrolyzers"], "0.4 7.4 11.4": ["exome"], "14.4 12.1 33.6": ["oniony"], "-0.7 -0.5 13.2": ["ving"], "8.0 14.8 33.6": ["tori"], "11.0 23.1 4.9": ["stalwartly"], "11.0 12.2 13.5": ["bodyslammed"], "-3.4 7.1 8.2": ["reinsmen"], "3.0 4.4 17.1": ["gayi"], "7.9 3.6 16.9": ["harvey"], "2.7 18.3 5.7": ["universalistic"], "11.1 29.1 11.3": ["djinn"], "14.6 13.9 12.5": ["indenting"], "10.7 2.2 13.6": ["bottleshop"], "19.4 11.4 21.5": ["spinny"], "14.5 9.7 12.3": ["tarnation"], "9.9 -0.9 16.9": ["aframaxes"], "8.8 32.5 5.9": ["outthinking"], "12.9 18.8 8.0": ["grotesqueness"], "10.0 -4.2 8.6": ["efore"], "12.9 17.1 17.0": ["guttersnipe"], "13.6 23.2 1.8": ["unhackable"], "10.1 5.8 8.9": ["jerrycan"], "9.4 4.8 15.5": ["objets"], "-9.2 3.6 4.2": ["undisbursed"], "13.6 6.9 15.6": ["pictographic"], "7.6 1.4 14.0": ["middleaged"], "-1.7 13.2 16.4": ["requite"], "19.9 37.4 12.7": ["elementals"], "12.1 0.6 9.1": ["weakish"], "4.9 16.0 9.6": ["cambers"], "8.0 5.8 9.2": ["skinnable"], "12.0 20.5 14.5": ["discombobulate"], "11.6 16.3 11.1": ["voyeuristically"], "12.3 -3.6 10.8": ["metalware"], "12.2 26.7 14.6": ["stockades"], "6.1 1.4 1.8": ["petrology"], "1.3 12.1 16.1": ["jaye"], "-4.5 2.9 13.3": ["dayshift"], "14.3 8.3 6.2": ["microbloggers"], "6.7 1.7 20.8": ["maillot"], "2.5 6.9 20.1": ["syntactically"], "13.4 -1.3 -0.5": ["entreprises"], "-2.8 22.3 2.5": ["sofar"], "8.3 6.2 13.9": ["kretek"], "16.1 9.8 21.4": ["terpsichorean"], "27.2 1.4 14.8": ["stringbean"], "10.0 6.3 4.9": ["soukous"], "17.3 0.6 9.0": ["raddled"], "-4.0 15.9 7.8": ["oncoprotein"], "14.5 17.4 10.3": ["shirtfront"], "5.7 6.6 23.2": ["shahtoosh"], "2.9 11.6 13.0": ["fourteener"], "-1.1 33.4 1.7": ["dispirit"], "8.3 -3.8 10.9": ["melodeon"], "0.6 -4.0 8.4": ["threesixty"], "1.0 4.4 2.2": ["phaco"], "8.1 12.8 5.8": ["gasser"], "-0.2 11.3 17.3": ["kamal"], "-0.3 1.2 10.4": ["outgrowers"], "17.3 7.4 9.1": ["golliwogs"], "6.0 7.2 23.0": ["vireos"], "7.8 10.1 14.3": ["txthinker"], "16.2 7.7 12.3": ["shamiana"], "9.2 13.2 9.8": ["mindfuck"], "12.0 11.4 19.4": ["potatoe"], "5.4 8.5 5.5": ["pleaders"], "-7.9 16.3 1.3": ["demined"], "4.5 4.0 29.6": ["pluots"], "17.0 6.9 22.4": ["chicle"], "10.5 5.5 23.0": ["nutmegs"], "-0.2 18.6 6.0": ["verbalization"], "-5.2 0.8 12.9": ["recertifications"], "1.8 9.5 9.1": ["neurotypical"], "-6.1 16.2 9.8": ["pitchability"], "-0.2 15.1 4.8": ["serialism"], "7.0 12.8 7.9": ["fogies"], "12.0 18.4 14.4": ["revoltingly"], "10.3 5.9 2.5": ["alredy"], "15.2 8.2 19.7": ["lolcats"], "-7.8 15.9 0.1": ["unpolitical"], "3.4 20.4 -2.3": ["disarrayed"], "2.6 10.0 10.1": ["stockpickers"], "4.3 12.7 7.1": ["halon"], "5.1 16.1 11.7": ["flavanoids"], "2.4 -4.4 12.8": ["milkings"], "1.1 6.1 6.2": ["xfy"], "8.5 16.4 12.7": ["travelin"], "15.4 21.2 11.2": ["exultantly"], "1.7 8.5 9.4": ["photochromic"], "7.9 -2.1 20.6": ["sportsfest"], "6.1 18.5 5.5": ["undistinguishable"], "4.3 1.5 5.7": ["paraben"], "0.7 9.3 13.2": ["varna"], "11.5 12.3 33.0": ["hoochies"], "4.8 11.8 8.7": ["keylock"], "21.1 8.3 20.7": ["sunned"], "-0.2 9.9 7.5": ["intraregional"], "2.0 4.5 19.3": ["twilights"], "8.1 9.2 16.2": ["pedicle"], "10.0 5.3 5.8": ["earnouts"], "9.9 9.9 9.6": ["quietens"], "12.8 2.9 12.1": ["bounciness"], "1.5 1.1 -0.6": ["wenn"], "8.1 8.5 -2.3": ["shoddier"], "12.3 12.5 10.0": ["penholder"], "11.2 10.9 32.4": ["mullein"], "1.0 16.4 0.8": ["misinforms"], "-0.2 22.3 3.9": ["meanspirited"], "4.6 8.9 16.4": ["deadheaded"], "6.5 7.6 10.9": ["mesmerizingly"], "18.9 6.5 17.6": ["jacarandas"], "20.0 19.5 20.8": ["ghoulies"], "0.5 1.4 19.3": ["chimi"], "13.6 6.5 15.5": ["serviettes"], "16.4 7.5 16.4": ["rouged"], "13.5 9.4 19.4": ["buckboard"], "10.1 27.5 5.4": ["eventualy"], "-3.9 8.1 8.7": ["dorsiflexion"], "-0.1 13.3 13.7": ["rab"], "3.0 -7.4 2.9": ["sixyear"], "10.9 12.0 9.9": ["cols", "guages"], "3.6 3.6 12.9": ["laetrile"], "21.6 10.7 5.8": ["endcaps"], "2.8 5.0 9.9": ["msl"], "14.3 21.5 4.8": ["darknet"], "9.6 4.3 15.5": ["suq"], "-10.4 -2.9 3.8": ["midwifes"], "0.0 2.3 8.8": ["ferric"], "-8.4 -6.6 5.9": ["studentships"], "13.7 13.3 19.4": ["downstroke"], "-2.9 12.8 4.9": ["inury"], "13.2 -5.2 15.5": ["xa"], "9.6 -10.2 24.1": ["wellington"], "4.0 -1.2 12.2": ["homeloans"], "7.3 18.8 15.0": ["spillers"], "-1.1 29.9 0.8": ["martyring"], "10.5 11.9 12.3": ["chorine"], "7.6 11.5 16.5": ["grandiloquence"], "5.1 26.5 -2.5": ["defamations"], "11.3 2.3 55.3": ["gurnard"], "18.9 -3.5 18.9": ["dro"], "4.1 9.6 10.0": ["photograms"], "7.5 8.4 11.0": ["joel"], "11.0 14.2 5.9": ["satanist"], "4.2 -1.9 14.5": ["programa"], "19.6 19.3 16.9": ["gorgon"], "2.5 6.5 14.4": ["sandra"], "6.8 8.6 11.8": ["downwardly"], "3.2 5.5 6.7": ["glossolalia"], "13.4 9.5 8.1": ["bureacratic"], "6.3 15.3 7.4": ["indomitability"], "-0.4 6.2 10.5": ["babywearing"], "-1.5 10.7 13.1": ["procyanidins"], "-2.6 8.6 6.3": ["cesses"], "7.0 13.5 7.3": ["restrengthen"], "15.4 12.9 21.4": ["sweetgum"], "2.9 7.5 4.9": ["elit"], "14.5 14.9 14.1": ["emergences"], "8.5 9.8 10.8": ["unbind"], "5.1 11.8 11.5": ["denz"], "9.7 10.6 4.7": ["submillimeter"], "25.2 17.8 6.3": ["landgrab"], "6.5 -1.9 3.5": ["flexography"], "8.8 12.4 27.8": ["winterberry"], "0.4 0.9 -6.0": ["reseat"], "-10.0 6.6 5.5": ["youngers"], "10.7 2.6 17.7": ["ballgirl"], "2.5 9.6 4.6": ["propoxur"], "4.5 5.0 16.7": ["jamu"], "10.0 2.1 6.1": ["microreactor"], "7.9 3.2 17.7": ["plushness"], "10.7 7.3 19.1": ["pushbikes"], "15.6 -1.1 46.0": ["salmons"], "11.7 9.0 17.2": ["sipes"], "12.9 6.4 7.1": ["voluminously"], "-7.3 5.5 -0.1": ["asid"], "2.6 20.3 3.3": ["chavistas"], "10.4 20.1 3.7": ["hawkishly"], "-0.9 1.4 -0.7": ["vists"], "9.3 -1.9 4.3": ["chloro"], "8.6 9.5 17.2": ["lysergic"], "-0.6 7.9 6.6": ["ira"], "6.3 18.3 5.6": ["legitimatize"], "7.4 10.5 23.2": ["wallaroo"], "1.9 20.3 6.2": ["sonia"], "6.5 11.9 19.9": ["maskless"], "15.0 15.9 4.4": ["malvertising"], "13.4 17.0 17.6": ["rood"], "11.3 2.0 9.0": ["palanquins"], "7.6 10.1 11.2": ["avtar"], "5.9 12.6 20.1": ["idylls"], "4.7 21.3 7.0": ["kundalini"], "9.8 6.9 1.3": ["tallish"], "4.3 17.7 45.5": ["linesiders"], "15.8 10.8 16.6": ["oxcart"], "10.6 0.6 -0.4": ["andwas"], "-7.4 9.4 0.2": ["excercised"], "-4.4 11.7 16.0": ["mele"], "19.6 12.0 12.0": ["magnetizing"], "2.5 -3.5 7.9": ["snowsport"], "14.2 6.7 15.5": ["sunbaking"], "11.1 7.3 18.4": ["cah"], "12.7 15.7 3.8": ["refind"], "11.8 17.8 21.1": ["itchin"], "0.5 11.3 8.9": ["bifurcations"], "6.4 8.1 1.8": ["dynamometers"], "2.2 8.9 42.7": ["fava"], "7.6 6.2 10.3": ["uraninite"], "4.6 13.7 3.6": ["dropzone"], "0.7 8.1 -2.7": ["comparisions"], "1.0 25.8 0.4": ["persuaders"], "5.6 8.4 32.7": ["kani"], "19.0 2.7 2.9": ["teck"], "0.9 7.7 14.6": ["polymerases"], "-1.5 20.8 9.8": ["senario"], "9.8 10.5 5.9": ["euroscepticism"], "5.6 11.1 18.0": ["curtsies"], "0.4 6.3 9.2": ["sanitariums"], "7.4 27.4 7.1": ["supplicate"], "5.7 3.9 23.8": ["roulades"], "11.4 14.4 10.6": ["beggared"], "12.2 8.8 10.7": ["insted"], "11.3 0.5 39.3": ["linguica"], "18.0 8.8 17.5": ["squeezer"], "5.6 11.3 2.2": ["thatn"], "5.1 8.1 1.2": ["miniaturise"], "2.5 10.8 19.7": ["endemism"], "-0.0 12.5 0.9": ["alligned"], "18.1 10.8 29.8": ["barnacled"], "6.2 12.0 3.6": ["senstive"], "21.3 9.8 31.7": ["sarnie"], "6.3 10.4 43.4": ["widgeon"], "4.3 20.8 2.5": ["antitheses"], "9.7 15.2 13.1": ["echochrome"], "3.9 17.0 6.8": ["safty"], "9.6 13.8 1.8": ["offroader"], "9.6 16.3 10.0": ["studier"], "9.8 24.5 8.3": ["reified"], "4.5 10.8 8.8": ["obbligato"], "2.4 20.6 1.8": ["communalising"], "1.0 -1.8 11.9": ["stakemoney"], "-4.5 5.3 9.2": ["retrocessional"], "0.6 4.1 1.8": ["dieses"], "5.8 19.7 20.9": ["armbars"], "14.8 1.0 12.9": ["smal"], "-7.9 13.2 9.3": ["keloid"], "11.0 14.3 9.9": ["enshroud"], "4.7 11.6 -2.2": ["manslaughters"], "-1.1 -6.2 14.6": ["ria"], "-10.4 1.5 3.0": ["studys"], "7.8 8.8 12.2": ["glenn"], "7.4 6.1 9.0": ["bullrider"], "-7.8 -10.3 9.8": ["cohosting"], "-4.8 8.4 8.7": ["ethambutol"], "21.8 4.5 15.3": ["macarena"], "17.7 13.5 28.9": ["windlass"], "4.5 8.7 11.3": ["midmajors"], "4.7 6.1 12.1": ["granitoid"], "-3.3 11.4 7.7": ["oppportunity"], "11.6 17.6 31.2": ["sterns"], "3.7 19.0 16.6": ["stuntwork"], "1.6 17.6 11.9": ["feminazi"], "4.5 7.4 9.8": ["uu"], "12.4 9.5 22.5": ["ochres"], "-8.4 -2.9 5.1": ["lutenist"], "5.5 14.2 7.6": ["humidify"], "8.2 -1.8 35.5": ["tamal"], "-9.8 9.2 -0.3": ["derogated"], "9.9 4.7 15.0": ["aliquot"], "8.6 6.7 15.9": ["measley"], "0.0 5.0 13.5": ["choro"], "0.2 12.6 15.7": ["keyphrase"], "9.9 1.5 11.7": ["wagonload"], "15.6 13.4 25.8": ["ocotillo"], "16.8 5.0 19.7": ["cartouche"], "11.4 2.2 -0.6": ["repitch"], "3.4 14.5 16.4": ["sailplanes"], "-3.0 11.7 4.0": ["mitzvos"], "10.9 3.9 7.9": ["paperboys"], "-6.0 1.6 4.3": ["lifeskills"], "4.6 6.5 11.0": ["plainsong"], "-5.1 12.8 8.5": ["kannada"], "-1.5 14.6 16.3": ["datable"], "0.7 19.0 6.1": ["desparation"], "14.9 3.2 1.6": ["ebank"], "14.2 4.7 8.9": ["apollo"], "0.5 8.0 7.8": ["straightahead"], "-5.9 -4.4 3.5": ["stabilities"], "-1.1 5.8 8.7": ["scond"], "-1.8 20.4 11.1": ["playtesting"], "-6.7 9.4 14.9": ["tillable"], "8.2 8.0 5.0": ["rumormongering"], "10.1 0.6 8.5": ["repertories"], "9.0 6.5 47.8": ["mahimahi"], "-2.7 11.9 10.8": ["unposted"], "19.8 -0.9 2.3": ["spruiks"], "13.0 8.5 13.3": ["aroud"], "11.2 25.8 15.5": ["scums"], "3.8 1.2 1.1": ["mcmd"], "1.1 14.1 5.4": ["crossbenches"], "-5.5 8.2 1.8": ["breathalyse"], "4.9 3.5 46.6": ["corvina"], "-3.9 1.9 1.5": ["quinidine"], "-0.9 16.5 2.9": ["critisize"], "-3.0 9.5 8.2": ["zoster"], "4.4 8.5 13.9": ["jarosite"], "16.4 9.5 12.2": ["thrums"], "4.7 -0.0 4.8": ["mima"], "1.5 11.4 5.3": ["centerlines"], "9.5 15.1 15.8": ["abrade"], "24.6 9.2 9.1": ["standee"], "6.0 -2.6 16.1": ["fay"], "2.6 14.8 14.4": ["earmarkers"], "8.9 16.3 0.5": ["rendezvousing"], "16.8 3.7 3.8": ["unt"], "0.8 7.2 1.3": ["reprioritisation"], "9.8 3.1 18.8": ["yukata"], "0.3 8.8 11.4": ["reimplanted"], "20.8 14.6 5.8": ["wobbliness"], "16.6 12.3 12.4": ["placemen"], "11.0 4.3 7.2": ["gabs"], "11.9 2.6 11.8": ["gearknob"], "10.5 7.3 8.8": ["substantiality"], "3.8 10.9 11.1": ["gaddi"], "12.3 30.1 10.8": ["necromancy"], "-2.3 7.8 2.1": ["intraosseous"], "23.8 9.6 9.0": ["alit"], "6.4 8.7 13.4": ["sassed", "moroccan"], "1.3 15.3 5.1": ["unfeigned"], "1.1 6.7 12.0": ["agad"], "2.4 5.1 5.0": ["nonmanagement"], "8.4 10.7 1.4": ["azide"], "19.8 8.2 23.9": ["soakers"], "20.8 6.2 14.7": ["candymakers"], "-1.6 13.9 12.0": ["aya"], "2.9 10.4 17.8": ["undrained"], "19.3 19.8 6.4": ["sulkily"], "-5.8 12.5 18.2": ["roomers"], "13.0 19.2 14.2": ["crankiest"], "15.7 8.8 17.1": ["persian"], "10.9 12.3 37.6": ["berried"], "4.2 9.9 12.7": ["artmaking"], "11.6 13.3 14.5": ["trainspotter"], "15.3 14.4 0.9": ["nostalgics"], "6.9 19.2 8.9": ["unlockers"], "16.8 8.7 34.9": ["deviled"], "3.7 1.8 -0.5": ["avait"], "7.6 6.6 6.9": ["iit"], "-1.9 4.5 17.8": ["bromelain"], "20.0 12.2 33.1": ["flatworm"], "0.2 15.7 14.9": ["tilth"], "5.8 7.5 18.4": ["dori"], "9.8 1.4 24.3": ["narra"], "9.3 27.9 8.2": ["splittism"], "11.9 7.3 3.1": ["moblogging"], "6.4 16.5 15.0": ["foreshocks"], "11.2 31.2 7.7": ["escapers"], "8.4 26.9 32.5": ["skeeter"], "17.9 4.7 6.8": ["brainbox"], "-0.9 10.8 -2.9": ["vehcile"], "8.1 0.3 -1.6": ["subsite"], "7.1 10.2 13.3": ["jacobs"], "9.7 2.3 4.3": ["punchcards"], "7.7 7.1 3.0": ["audioconferencing"], "6.6 -2.8 -0.3": ["immunodiagnostics"], "12.8 5.5 -6.4": ["junaio"], "19.8 22.5 27.2": ["saltshaker"], "11.8 0.5 29.1": ["frybread"], "-1.7 4.7 12.9": ["lopez"], "7.2 -0.9 9.8": ["sulla"], "9.5 14.6 14.1": ["bunkbeds"], "22.9 -0.8 4.1": ["clacked"], "5.3 11.2 18.7": ["subglacial"], "6.2 -4.1 11.5": ["vay"], "0.4 3.5 7.9": ["richardson"], "9.9 9.5 9.4": ["challengingly"], "-4.0 14.6 2.8": ["revictimized"], "3.3 -2.9 3.1": ["careeer"], "2.9 0.9 13.6": ["costumey"], "16.2 -5.3 -3.1": ["exlusive"], "14.2 13.5 24.2": ["regrows"], "0.2 1.3 20.7": ["parsons"], "5.1 14.1 13.8": ["mistime"], "8.1 12.2 4.0": ["exactingly"], "3.6 11.9 3.4": ["nonsection"], "12.2 3.3 14.6": ["cruft"], "5.4 -2.9 12.6": ["checkweigher"], "-0.2 17.6 17.8": ["overgraze"], "14.0 6.4 18.0": ["massachusetts"], "12.7 11.1 -1.2": ["obssessed"], "11.5 11.8 14.3": ["lumbago"], "18.7 15.5 13.2": ["hoardes"], "5.5 5.3 14.7": ["gabbroic"], "-10.7 7.2 4.7": ["signable"], "4.5 4.4 3.7": ["innercity"], "4.8 6.4 1.1": ["multicasts"], "-1.3 10.0 -2.4": ["criticsm"], "3.1 7.2 -4.6": ["encryptor"], "4.6 16.9 10.5": ["desaparecidos"], "7.4 17.4 13.1": ["footpeg"], "9.2 15.9 21.2": ["uranage"], "7.7 1.9 0.6": ["subpeona"], "16.7 20.2 11.2": ["atomize"], "10.7 19.4 38.2": ["handline"], "7.1 7.4 34.3": ["tabouleh"], "5.4 24.6 13.6": ["imposture"], "0.6 8.1 18.8": ["dadah"], "8.4 9.7 8.9": ["piezoelectrics"], "14.6 -5.8 22.7": ["quiffs"], "12.5 4.2 25.8": ["appaloosa"], "4.2 10.8 1.2": ["beem"], "0.3 1.3 -0.2": ["palonosetron"], "-1.2 -5.0 8.6": ["titre"], "-9.3 12.9 7.0": ["unwitnessed"], "22.2 17.4 30.5": ["fathead"], "7.6 19.6 14.8": ["linkbait"], "13.4 0.1 -2.9": ["puchase"], "11.9 10.5 10.0": ["glocal"], "6.5 20.2 21.5": ["herbivory"], "8.2 1.9 8.2": ["wjh"], "0.8 14.8 7.3": ["peating"], "24.0 7.0 26.5": ["pincushions"], "-5.1 7.9 11.6": ["chondrosarcoma"], "6.4 5.2 16.6": ["taga"], "7.0 37.0 3.6": ["antisemites"], "-5.4 12.6 1.9": ["criminological"], "-2.5 8.5 8.7": ["mony"], "-4.1 15.2 -8.2": ["suicided"], "10.3 4.2 7.4": ["connecter"], "0.0 2.1 6.7": ["facialist"], "6.8 10.3 11.7": ["theywere"], "6.1 4.2 21.8": ["gelatins"], "3.6 4.0 5.0": ["emeriti"], "-9.3 -6.7 7.2": ["sharemilking"], "-2.0 12.8 13.0": ["jeet"], "4.6 10.4 5.9": ["sidelocks"], "22.0 10.4 6.7": ["highwire"], "-0.1 10.9 13.5": ["synesthetes", "prefetch"], "-0.9 6.3 10.7": ["exfoliants"], "-0.2 18.0 6.3": ["transcendentalist"], "7.4 9.2 0.4": ["compaign"], "-2.5 21.8 8.5": ["symptomatically"], "8.8 2.5 13.7": ["trannie"], "6.1 12.6 12.5": ["prognosed"], "7.7 15.1 9.7": ["nauseates"], "0.4 3.5 -1.0": ["weiter"], "5.8 2.9 10.4": ["qed"], "0.4 15.8 21.3": ["flexitarian"], "10.1 12.5 5.8": ["uch"], "10.6 6.9 -5.4": ["fromer"], "5.0 9.9 3.9": ["havnt"], "14.3 6.8 18.5": ["cryogenically"], "1.1 6.1 1.4": ["consenus"], "7.9 13.6 14.7": ["hyperpartisanship"], "10.8 26.7 5.2": ["primitiveness"], "8.8 6.1 11.4": ["floorcovering"], "7.4 14.5 11.7": ["slashtags"], "3.6 26.4 14.4": ["gainline"], "2.4 2.2 -0.2": ["ecd"], "4.0 4.8 16.5": ["thu"], "5.3 -0.2 26.2": ["cai"], "2.6 21.2 7.7": ["sunni"], "17.2 14.6 28.0": ["salvager"], "1.2 21.1 15.1": ["shotting"], "3.3 -0.2 -3.1": ["oximeter"], "10.3 7.2 15.3": ["posho"], "0.5 14.6 14.5": ["overwatered"], "-12.1 7.4 4.3": ["wiill"], "-2.1 0.4 14.5": ["culpa"], "2.6 3.1 17.5": ["clearwell"], "-2.1 27.3 6.3": ["chavismo"], "9.8 3.3 9.2": ["cryostat"], "-4.0 10.8 13.5": ["backloading"], "20.8 11.4 13.4": ["enlarger"], "19.0 8.8 13.8": ["doohickeys", "domelike"], "2.0 11.6 9.9": ["walt"], "5.6 12.3 6.9": ["dumpee"], "6.4 11.9 15.2": ["grimey"], "6.6 3.6 11.1": ["ghax"], "17.2 12.8 13.8": ["egads"], "4.9 2.5 10.7": ["photobioreactor"], "4.8 15.5 14.1": ["hara"], "8.3 10.1 27.0": ["heuchera"], "-2.9 21.1 3.0": ["bandsman"], "10.2 5.1 12.5": ["orf"], "9.4 18.0 10.2": ["maximalism"], "8.6 10.8 5.3": ["cardiomyocyte"], "5.7 3.9 8.5": ["glycobiology"], "-3.2 9.2 1.4": ["dischargeability"], "8.4 -2.4 4.7": ["firstclass"], "-1.9 5.9 -1.5": ["auscultation"], "6.0 12.5 8.2": ["unroofed"], "10.5 12.0 8.5": ["motorhead"], "14.4 11.8 2.7": ["unsubtly"], "15.4 2.5 1.5": ["rts"], "25.4 5.0 23.0": ["stix"], "4.7 10.8 2.4": ["unrealisable"], "-1.7 8.6 5.6": ["assesments"], "2.4 12.2 3.5": ["shuld"], "-1.1 19.2 -3.5": ["mordantly"], "9.1 10.9 10.8": ["sizeof"], "21.0 14.1 15.9": ["offshores"], "-0.5 15.8 4.5": ["disjuncture"], "15.5 0.4 13.8": ["stencilling"], "2.4 4.9 -4.2": ["critised"], "-5.2 6.5 4.1": ["hepatocellular"], "0.3 5.4 -0.3": ["dapd"], "8.0 11.1 1.7": ["solidary"], "-3.1 19.7 0.2": ["religon"], "7.4 6.1 5.6": ["nanopositioning"], "8.6 13.0 12.2": ["shticks"], "6.5 3.7 18.5": ["rockbottom"], "7.0 2.5 3.2": ["streeted"], "12.7 26.7 14.4": ["conniver"], "12.8 -2.5 9.5": ["trn"], "-0.9 23.4 1.2": ["oposition"], "10.2 8.4 7.2": ["stiker"], "16.5 -1.0 13.9": ["flacon"], "-2.9 27.0 1.9": ["fulminates"], "11.1 4.1 13.4": ["haver"], "29.4 19.2 28.8": ["giantess"], "13.5 4.9 6.7": ["equitise"], "4.0 4.3 -1.2": ["acquited"], "4.6 27.1 14.8": ["multimission"], "3.2 6.0 21.1": ["laff"], "-16.3 4.2 4.9": ["shiur"], "8.8 2.4 16.6": ["respray"], "9.5 5.4 14.0": ["bioswale"], "1.0 17.5 16.8": ["commensal"], "-1.0 16.0 8.3": ["subluxations"], "19.6 11.5 38.5": ["amphipod"], "-6.2 3.2 2.3": ["crystalens"], "17.5 7.2 11.7": ["gawks"], "12.0 14.1 5.7": ["sakawa"], "15.7 7.9 3.1": ["eminating"], "1.6 10.6 16.4": ["fibonacci"], "11.2 11.7 7.9": ["pefect"], "6.3 6.6 11.5": ["haa"], "-1.0 12.0 8.6": ["formline"], "9.9 0.3 30.4": ["haluski"], "13.0 17.5 21.9": ["wharfies"], "5.4 15.4 25.7": ["bosun"], "-8.5 0.3 6.1": ["stillborns"], "3.5 5.6 7.5": ["margaret"], "1.0 13.9 0.4": ["universalized"], "7.2 15.5 6.6": ["redounds"], "12.8 2.3 8.6": ["mammas"], "1.2 10.3 4.9": ["traffice"], "9.5 16.0 8.1": ["mudra"], "23.2 14.8 24.5": ["phoenixes"], "-4.0 3.9 6.6": ["excellant"], "5.2 5.9 3.3": ["representin"], "3.8 8.9 17.6": ["praziquantel"], "10.2 15.5 -2.6": ["bulletproofing"], "3.4 0.8 15.3": ["cashmeres"], "2.7 14.7 1.5": ["streakiest"], "-9.0 8.7 6.8": ["isochronous"], "6.3 24.4 17.1": ["thumbsticks"], "14.7 16.1 18.2": ["habour"], "13.2 6.3 5.5": ["teir"], "5.0 12.6 41.1": ["longliner"], "-3.4 5.5 0.2": ["thegame"], "5.1 4.6 13.7": ["shelties"], "25.7 22.5 15.8": ["unobtainium"], "7.3 14.5 16.3": ["reddy"], "1.0 9.7 10.1": ["akhara"], "-3.6 9.7 4.3": ["indinavir"], "5.3 -2.5 8.0": ["cing"], "3.3 4.5 13.0": ["geosynthetic"], "5.7 13.8 13.0": ["collagist"], "-1.8 15.9 1.3": ["obvioulsy"], "-5.4 7.9 7.2": ["nociceptive"], "1.0 21.3 3.7": ["critize"], "-2.5 5.0 21.8": ["masoor"], "6.6 17.3 16.1": ["trapo"], "-1.3 12.5 0.2": ["quietist"], "8.3 6.2 1.9": ["nearshoring"], "-1.2 9.3 4.3": ["alkylation"], "-2.2 7.1 6.4": ["limns"], "4.8 16.9 13.5": ["undefiled"], "-5.7 -2.7 4.6": ["transrating"], "0.2 13.4 -1.5": ["mediatory"], "9.8 6.5 26.6": ["krater"], "21.4 15.7 20.2": ["whiskery"], "1.3 15.1 7.2": ["nitpicker"], "14.1 26.2 11.4": ["malwares"], "18.3 20.9 24.2": ["blowpipe"], "6.9 25.9 11.4": ["literalness"], "-5.1 6.3 5.3": ["pyelonephritis"], "11.7 6.0 3.4": ["yesteray"], "6.1 7.9 1.6": ["protg"], "1.0 3.0 15.4": ["vit"], "9.9 5.8 8.8": ["kinescope"], "4.1 11.2 6.1": ["tooo"], "13.2 9.7 10.0": ["geekish"], "2.5 7.6 0.1": ["indentification"], "12.6 8.9 23.2": ["sporrans"], "-4.1 -5.5 -5.0": ["includingthe"], "10.1 13.6 6.4": ["gamelike"], "2.3 7.7 11.0": ["toback"], "10.8 9.3 10.1": ["doofy"], "-1.9 -3.0 10.5": ["kenneling"], "10.8 3.0 2.5": ["thje"], "15.4 2.0 0.8": ["lifescience"], "0.5 -1.3 3.6": ["sitewide"], "-2.8 8.8 18.4": ["culinarily"], "20.0 8.9 34.3": ["plumpest"], "-0.9 1.4 6.7": ["reprioritised"], "14.6 5.1 5.4": ["forst"], "14.4 -12.0 -0.7": ["rasied"], "-3.5 17.5 10.5": ["tupuna"], "4.3 3.3 3.7": ["prudency"], "8.7 -3.0 -2.1": ["surburb"], "18.4 8.4 39.1": ["jujubes"], "3.1 13.0 7.0": ["afferent"], "6.0 7.5 11.2": ["coleman"], "5.6 5.5 8.4": ["tylenol"], "-3.9 11.7 10.6": ["reacclimated"], "6.4 0.1 9.0": ["buget"], "1.7 1.7 7.4": ["ministryministry"], "2.2 0.5 31.4": ["ayam"], "-1.2 -1.2 21.3": ["limerock"], "2.0 3.6 21.0": ["skeds"], "22.3 2.3 8.9": ["aroundthe"], "6.6 7.1 17.2": ["foliated"], "6.9 7.8 6.4": ["exagerated"], "-5.8 6.9 2.1": ["immunomodulating"], "-2.7 9.4 -3.7": ["advocator"], "5.0 14.7 -0.2": ["abstentia"], "10.5 7.1 16.5": ["springhouse"], "25.2 6.4 8.0": ["giddying"], "14.7 20.9 20.2": ["micrometeoroids"], "7.4 6.7 11.7": ["glassings"], "17.0 13.3 11.3": ["grillwork"], "16.2 3.5 7.5": ["circuslike"], "9.1 2.0 11.4": ["bibliog"], "6.9 11.5 13.0": ["shortener"], "-0.9 1.7 -0.4": ["coment"], "10.3 -2.7 -3.2": ["companyprofile"], "-0.2 19.9 7.5": ["idealogue"], "4.8 7.1 24.2": ["ladoos"], "0.5 18.0 9.7": ["congruity"], "14.9 14.5 10.1": ["pissant"], "6.7 8.4 10.1": ["energizers"], "21.3 23.8 18.7": ["devourer"], "21.3 6.5 11.1": ["mentalists"], "7.2 11.3 -5.9": ["advocation"], "-0.0 18.5 -2.1": ["perseverant"], "1.7 0.4 -0.8": ["steno"], "11.6 13.1 25.2": ["slushes"], "7.2 12.1 0.7": ["unspectacularly"], "15.2 10.6 2.7": ["fandemonium"], "29.0 14.8 18.5": ["oilrigs"], "5.1 5.0 17.4": ["paula"], "5.0 2.7 9.6": ["gaa"], "13.4 17.7 13.3": ["ghastliness"], "13.4 12.9 3.9": ["watchdogging"], "10.7 0.8 -1.4": ["audiovisuals"], "4.8 7.7 21.3": ["sandesh"], "-6.8 -0.2 4.1": ["prelaw"], "0.9 7.0 8.4": ["commonman"], "4.6 1.7 6.9": ["racings"], "10.1 7.2 14.9": ["bricolage"], "-5.4 5.6 -0.1": ["denaturing"], "3.8 7.2 12.9": ["clevudine"], "8.9 7.5 14.7": ["semaphores"], "8.2 17.3 3.8": ["ingratiated"], "15.3 3.0 20.2": ["aproned"], "1.4 12.7 10.1": ["significances"], "10.1 5.7 13.0": ["pitchblende"], "-3.1 5.5 0.4": ["appertaining"], "0.6 18.9 11.4": ["fungicidal"], "-5.6 19.2 -2.7": ["violences"], "11.3 8.4 -1.2": ["ersol"], "14.7 10.4 7.9": ["boeing"], "14.1 8.0 7.0": ["shrills"], "18.7 0.8 11.2": ["hsbc"], "0.4 5.9 3.1": ["entacapone"], "-2.5 11.6 6.4": ["sant"], "8.3 5.4 8.3": ["itemise"], "-7.8 -6.0 6.4": ["recyclate"], "8.1 12.0 42.1": ["wakame"], "4.3 10.0 -3.6": ["mcjoan"], "3.2 -3.6 11.3": ["tbd"], "-3.9 21.2 1.6": ["respecters"], "4.5 8.7 15.1": ["dzud"], "19.2 20.9 6.8": ["nanobot"], "8.1 9.7 4.0": ["eli"], "6.4 15.5 11.7": ["absentmindedness"], "-0.0 5.4 5.0": ["anastomoses"], "4.1 5.6 8.5": ["boosterish"], "32.3 17.1 6.2": ["bestriding"], "8.5 -0.6 -3.7": ["cardless"], "14.8 -0.4 10.0": ["clomped"], "-3.3 8.7 5.8": ["replevin"], "9.6 2.8 15.5": ["bermudas"], "-4.2 10.8 0.4": ["trackage"], "-2.3 16.3 7.1": ["italicize"], "7.6 14.6 11.1": ["malcode"], "7.7 11.5 2.5": ["lionhearted"], "10.2 3.8 -1.0": ["deemphasizing"], "1.7 5.2 12.2": ["gana"], "3.7 12.0 6.3": ["aproach"], "6.8 12.7 19.3": ["gossanous"], "12.3 28.1 5.6": ["deafeningly"], "9.2 10.1 6.5": ["shofars"], "1.8 6.8 27.4": ["celosia"], "4.6 5.4 18.3": ["charleston"], "11.6 7.2 11.7": ["casanova"], "5.8 7.7 8.4": ["unversed"], "9.5 10.4 6.6": ["cagefighter"], "5.6 2.5 6.7": ["deo"], "0.2 11.5 8.9": ["lateraling"], "1.8 2.8 27.0": ["rearers"], "8.4 13.1 14.0": ["eavestroughs"], "25.4 4.4 18.5": ["octo"], "7.2 16.3 9.3": ["guilts"], "7.9 19.7 7.6": ["depicter"], "0.2 21.6 15.3": ["prestart"], "3.0 2.5 0.8": ["geoscientific"], "12.9 10.1 17.8": ["milkmaids"], "1.3 10.3 17.2": ["endoderm"], "0.3 6.8 4.0": ["nitrosamine"], "7.5 3.4 22.5": ["salver"], "19.3 3.6 9.3": ["boardwear"], "-1.3 9.4 6.5": ["dural"], "13.4 14.9 4.0": ["backslash"], "8.9 21.2 9.6": ["perfectibility"], "14.2 2.8 14.1": ["brickyards"], "25.3 11.7 25.9": ["dreamcatcher"], "14.5 8.9 16.6": ["bingers"], "-1.2 9.9 1.8": ["decission"], "-0.6 6.9 5.4": ["diplopia"], "-1.4 18.4 8.7": ["bantustan"], "8.0 9.9 11.4": ["wassup"], "14.2 21.9 7.5": ["codebreaking"], "13.2 10.3 31.3": ["snorkelled"], "7.3 5.9 13.1": ["organismal"], "17.2 5.1 49.4": ["mackerels"], "17.9 3.9 7.6": ["newsbrief"], "0.1 0.9 -3.3": ["izmocars"], "15.2 19.2 19.5": ["soliton"], "2.0 -5.7 -11.5": ["nternational"], "5.8 25.6 6.7": ["ungratefulness"], "-3.8 18.4 10.6": ["understandingly"], "-5.7 3.0 11.7": ["lear"], "3.4 8.1 10.3": ["dacetuzumab"], "14.1 20.9 10.6": ["shittiest"], "11.2 18.0 9.2": ["daydreamers"], "-10.1 5.3 -1.3": ["paraphilia"], "6.1 13.4 5.8": ["frostily"], "17.0 9.5 21.1": ["ironmongery"], "17.6 4.0 6.8": ["centurylong"], "5.9 4.8 18.3": ["classico"], "-13.3 -2.6 1.5": ["triennium"], "12.8 14.3 13.8": ["hugo"], "5.1 11.2 10.3": ["openpit"], "2.7 6.8 14.4": ["kinkier"], "19.0 13.2 6.7": ["tonk"], "5.9 12.1 10.4": ["circumnavigations"], "6.7 2.9 4.0": ["dampner"], "12.2 6.3 17.1": ["colorizing"], "12.4 4.8 14.3": ["herbology"], "25.3 5.4 16.4": ["offa"], "7.1 14.5 9.1": ["iframes"], "-1.4 13.2 4.3": ["regretable"], "2.5 1.9 11.3": ["reappropriated"], "-0.2 5.5 24.0": ["methi"], "5.8 3.1 4.0": ["microseismic"], "5.4 12.0 2.0": ["wirings"], "-3.6 6.2 -3.3": ["sensorless"], "1.8 10.6 4.6": ["wouldl"], "17.4 -5.1 9.0": ["billionairess"], "5.7 -2.8 7.1": ["bioresorbable"], "12.4 4.9 12.9": ["clucky"], "-1.2 19.4 10.4": ["readapt"], "9.6 9.5 14.4": ["copses"], "-1.9 2.0 12.6": ["austenitic"], "2.5 -2.4 4.8": ["maintenances"], "1.1 19.8 11.2": ["loveth"], "3.2 -3.5 13.6": ["habang"], "7.8 4.0 7.1": ["paleoanthropology"], "2.7 11.9 10.8": ["postlude"], "10.1 6.0 2.3": ["equipement"], "-1.0 10.9 0.9": ["pracharak"], "-0.0 5.4 3.7": ["assualted"], "1.1 12.0 -4.1": ["decongested"], "15.4 3.8 5.0": ["noncompetition"], "5.0 4.8 7.3": ["bionanotechnology"], "5.1 1.5 8.6": ["midcycle"], "21.8 8.9 46.3": ["gilled"], "4.2 7.3 15.2": ["nigra"], "-1.9 0.2 8.5": ["yera"], "17.4 12.5 8.7": ["hypno"], "3.9 8.4 22.1": ["sativa"], "6.8 3.0 15.9": ["hannah"], "22.0 5.0 11.2": ["backflipping"], "-0.1 12.4 12.3": ["shel"], "-3.8 3.4 2.8": ["affd"], "4.8 8.1 20.0": ["vt"], "-7.7 3.1 -2.0": ["graphologist"], "24.5 10.5 20.8": ["checkerboards"], "6.8 9.2 16.7": ["tonalite"], "2.1 16.5 13.1": ["shootoff"], "1.7 3.9 9.4": ["viscosupplementation"], "9.0 14.0 10.4": ["cravers"], "8.7 11.3 28.5": ["crawfishing"], "22.3 18.5 10.7": ["snakepit"], "2.8 9.1 7.4": ["lamellar"], "0.2 7.7 13.8": ["cli"], "1.8 2.4 9.1": ["biospecimen"], "5.2 20.0 6.3": ["hospitably"], "8.8 8.4 20.1": ["revegetated"], "4.6 19.2 8.5": ["assinine"], "9.3 7.0 12.6": ["polybag", "widdled"], "9.8 0.1 6.8": ["pipefitting"], "0.0 5.5 6.4": ["patwaris"], "-0.5 17.6 12.4": ["fellowshipping"], "-3.5 7.1 6.7": ["gamehigh"], "2.9 3.8 4.8": ["atherogenic"], "3.0 19.6 5.2": ["heelish"], "6.5 11.6 37.5": ["bluebills"], "2.2 15.6 2.9": ["disinhibited"], "21.8 23.4 22.6": ["amazons"], "17.8 14.0 14.8": ["bandito"], "8.8 0.6 12.8": ["gameroom"], "4.6 2.2 13.0": ["joong"], "7.2 0.2 7.2": ["tramcars"], "1.4 -3.2 14.4": ["kas"], "3.3 -5.0 1.4": ["kwanzas"], "0.3 11.3 11.0": ["couponers"], "2.9 8.1 9.1": ["halide"], "11.0 25.4 24.1": ["cutworm"], "-1.2 11.3 15.7": ["stopbanks"], "12.3 10.1 21.4": ["hankerin"], "-0.7 13.7 5.1": ["polynomials"], "6.1 -1.6 15.5": ["velo"], "-0.4 10.3 8.4": ["gravesides"], "2.8 8.3 10.3": ["sutlers"], "5.6 5.5 12.4": ["gonadal", "dechlorination"], "25.7 26.1 17.4": ["fecklessly"], "1.8 -1.6 4.1": ["transitionary"], "4.2 26.3 8.5": ["warding"], "6.1 10.6 17.2": ["mura"], "17.5 1.6 13.7": ["glugging"], "14.6 11.0 38.8": ["madrone"], "5.4 24.8 3.5": ["warfronts"], "-5.6 19.1 -1.9": ["personnal"], "4.8 8.3 7.5": ["kiun"], "11.7 11.9 6.7": ["photocells"], "8.2 1.9 5.2": ["ultraclean"], "2.2 18.7 4.4": ["inconsideration"], "10.5 9.4 4.7": ["superinjunction"], "11.8 10.8 3.2": ["hotzone"], "14.9 15.8 28.4": ["longtail"], "2.0 8.7 15.5": ["unmineralized"], "5.9 4.6 5.4": ["maintence"], "-3.4 4.9 8.8": ["oropharyngeal"], "6.6 -5.7 9.1": ["spiffs"], "15.6 12.3 12.4": ["sourest"], "-4.4 25.6 15.1": ["fraternisation"], "0.5 17.0 20.9": ["pickney"], "-3.2 8.6 -0.8": ["dysplastic"], "0.9 8.7 -0.6": ["clueing"], "9.8 15.5 3.3": ["depressurisation"], "1.1 7.4 5.7": ["prepsters"], "8.3 8.3 6.1": ["saudi"], "5.1 11.9 11.6": ["superfights"], "0.3 5.4 -0.2": ["turbodiesels"], "3.4 24.4 8.6": ["expediencies"], "-7.2 6.9 -6.2": ["ommitted"], "10.7 8.5 8.2": ["balafon"], "6.0 4.9 7.8": ["saddler"], "-1.9 6.6 16.5": ["pura"], "-4.7 2.6 9.0": ["reccommend"], "19.2 -6.4 -5.2": ["orignally"], "5.0 -0.6 9.7": ["widenings"], "8.4 11.3 12.1": ["defriend"], "8.8 0.5 9.5": ["worldbeat"], "1.5 -6.4 14.5": ["shaggier"], "-2.5 6.7 8.9": ["liturgically"], "1.3 12.3 6.1": ["cleansheet"], "19.1 6.4 32.8": ["silverbeet"], "12.7 -2.4 17.8": ["gilet"], "15.4 4.8 5.2": ["debtload"], "16.9 6.3 31.3": ["hadrosaurs"], "14.2 16.4 22.3": ["rhombus"], "27.9 8.0 -0.2": ["subsid"], "-12.1 -2.6 -6.3": ["reftel"], "14.0 2.4 -5.2": ["barechested"], "-0.8 9.6 5.6": ["safey"], "4.0 2.2 8.2": ["elastane"], "-3.6 4.4 12.2": ["disbarring"], "-12.6 -6.7 8.4": ["tution"], "3.5 30.2 2.1": ["subalterns"], "-2.4 11.6 6.3": ["commissionaires"], "19.7 0.7 10.2": ["toteboard"], "-9.4 15.0 10.3": ["famlies"], "-0.5 9.1 6.9": ["outkicking"], "22.7 25.1 11.3": ["pinioned"], "8.7 16.6 1.7": ["intruiging"], "-5.8 8.1 7.6": ["priveleged"], "7.9 -0.3 28.7": ["multicourse"], "7.3 10.2 20.3": ["overstuffing"], "2.3 10.8 5.5": ["dollarized"], "14.0 3.3 16.1": ["lambada"], "6.2 1.6 14.1": ["cystine"], "3.0 8.3 3.5": ["hightened"], "13.3 20.4 28.0": ["dropshots"], "-7.4 6.7 -1.7": ["chlorpromazine"], "-2.2 9.8 7.8": ["terseness"], "10.4 10.7 21.6": ["felafel"], "10.1 26.0 7.7": ["illiberalism"], "0.8 7.4 9.1": ["twelth"], "-8.2 3.0 6.9": ["cancelable"], "3.7 9.7 4.2": ["administrational"], "5.1 13.9 16.8": ["rightbehind"], "11.1 13.2 15.2": ["opposable"], "13.4 10.3 12.3": ["rollbar"], "2.7 10.4 -1.0": ["baptising"], "-4.9 5.1 -0.5": ["pradefovir"], "-4.6 -0.8 10.1": ["tiatr"], "7.6 9.5 17.3": ["winer"], "1.6 8.2 5.2": ["lymphadenopathy"], "1.3 2.6 19.3": ["prewashed"], "3.5 22.5 14.2": ["trepidatious"], "2.0 8.9 5.2": ["neurexin"], "11.8 11.1 8.5": ["descender"], "5.0 5.1 10.4": ["grungier"], "6.5 5.0 1.0": ["overprescribe"], "4.1 10.0 2.1": ["inhomogeneous"], "4.9 14.1 15.2": ["triskaidekaphobia"], "5.6 16.0 17.0": ["backbend"], "7.1 4.4 20.2": ["byelaw"], "23.8 12.4 16.8": ["elfish"], "11.2 0.3 6.2": ["tacho"], "13.7 17.9 8.0": ["seppuku"], "-2.6 0.6 13.7": ["masyadong"], "-4.6 20.0 9.2": ["compartmentalisation"], "8.9 7.2 1.7": ["previsualization"], "0.6 5.8 14.6": ["ecozones"], "2.1 3.8 4.4": ["moeny"], "11.6 15.8 10.1": ["africans"], "-12.9 1.9 6.4": ["annotator"], "1.4 15.3 21.5": ["overdrinking"], "4.8 13.8 6.9": ["beca"], "12.4 16.5 18.9": ["swatters"], "-0.2 2.7 4.7": ["devistated"], "0.8 -8.4 2.4": ["requirment"], "5.0 17.9 7.7": ["lif"], "4.7 3.6 17.2": ["hybridizer"], "7.7 8.1 10.2": ["ipl"], "7.5 -5.5 8.6": ["proofer"], "1.5 1.0 9.3": ["serializer"], "-2.1 13.5 13.4": ["microevolution"], "11.8 6.2 20.7": ["megafarms"], "10.9 13.8 29.4": ["eggless"], "3.8 -2.4 16.7": ["suffolk"], "24.3 8.2 16.5": ["sunbursts"], "17.3 10.4 22.5": ["cavewoman"], "9.7 22.5 10.3": ["fuelers"], "15.7 20.5 14.2": ["tamers"], "9.6 11.9 16.0": ["jugaad"], "4.4 5.1 6.5": ["bingle"], "6.6 7.4 14.2": ["bated"], "8.6 7.2 28.7": ["arils"], "13.0 24.7 6.3": ["defanging"], "-2.9 17.1 11.1": ["inartfully"], "7.5 -3.1 10.4": ["newydd"], "4.7 9.6 -3.2": ["habitue"], "16.8 9.9 10.1": ["cheezy"], "4.7 9.9 7.8": ["mili"], "5.5 5.1 20.4": ["deadstock"], "2.7 7.5 7.7": ["phospho"], "6.3 6.9 46.3": ["skipjacks"], "3.3 9.5 3.3": ["vaccinology"], "10.0 13.0 11.6": ["doorpost"], "-7.8 1.0 6.0": ["tertile"], "8.4 5.6 10.5": ["curlies"], "-6.5 4.4 -2.2": ["competant"], "13.5 9.3 15.6": ["hamburg"], "3.0 24.0 12.9": ["unmuzzled"], "8.0 17.9 1.6": ["globality"], "-10.2 3.5 0.8": ["nebulization"], "17.5 8.0 5.7": ["avalanched"], "-5.8 -4.2 2.3": ["immunodiagnostic"], "22.5 22.6 20.5": ["zombielike"], "3.6 6.6 27.9": ["ladleful"], "-3.2 4.8 10.6": ["claudin"], "5.7 20.6 4.8": ["badmouths"], "6.8 12.6 13.4": ["freediver"], "21.1 11.9 17.9": ["phonemakers"], "-6.2 15.0 5.6": ["deconditioning"], "3.6 2.6 7.4": ["remortgagers"], "5.0 25.2 7.3": ["rouges"], "1.7 14.2 8.0": ["anidulafungin"], "5.3 14.6 4.7": ["parsecs"], "9.3 12.8 16.4": ["rightmost"], "-2.1 2.7 19.6": ["haldi"], "4.6 7.9 9.1": ["wonderin"], "-8.0 -5.5 6.2": ["sunsetted"], "-8.2 -1.2 12.5": ["nonregistered"], "8.7 30.1 11.0": ["regressives"], "-0.4 14.5 -0.5": ["detractions"], "18.2 6.5 18.0": ["pillowed"], "12.1 12.3 26.3": ["lusciousness"], "0.2 2.2 15.6": ["angie"], "3.3 9.6 9.5": ["washeries"], "13.7 24.7 17.8": ["atavism"], "9.1 11.8 3.7": ["kannuu"], "7.6 5.1 9.2": ["minijack"], "-1.7 19.3 11.0": ["slangs"], "1.7 8.1 15.3": ["dentine"], "8.8 -0.2 13.5": ["scrimps"], "18.1 5.8 13.6": ["bonneted"], "7.2 16.5 8.9": ["defocus"], "12.3 1.0 9.5": ["otros"], "20.7 0.3 13.8": ["laggardly"], "7.3 7.9 6.7": ["ogg"], "10.0 10.7 14.0": ["gutbucket"], "0.8 20.0 4.0": ["cuttingly"], "4.4 6.5 10.0": ["intraleague"], "-0.8 14.0 2.1": ["actioning"], "1.6 -11.1 5.6": ["readvertised"], "-0.5 6.2 16.2": ["nontypical"], "0.3 10.8 1.5": ["helpin"], "8.6 11.3 8.8": ["jackaroo"], "13.4 19.0 5.3": ["suddently"], "7.8 24.0 14.8": ["artlessness"], "12.6 11.9 29.0": ["jigheads"], "6.1 6.3 16.3": ["baaaaack"], "7.7 5.8 11.3": ["retinues"], "4.1 29.7 9.8": ["rapine"], "5.5 10.7 10.8": ["somwhere"], "6.5 -1.6 14.0": ["precrisis"], "10.1 -4.4 34.4": ["parmigiano"], "-3.8 10.4 8.3": ["glycosylated"], "8.5 6.6 21.5": ["ascii"], "16.2 10.3 10.9": ["lappy"], "3.2 20.5 10.4": ["hypocrits"], "15.9 10.3 23.4": ["freckly"], "5.6 5.5 -5.3": ["mobilizers"], "1.0 9.8 13.1": ["piecemealing"], "-10.5 12.1 7.0": ["comprehensibility"], "-7.8 0.3 15.7": ["jurying"], "6.0 8.8 9.1": ["makeing"], "1.9 -2.2 7.5": ["trichlorosilane"], "10.9 15.3 8.2": ["trine"], "9.2 14.6 15.3": ["butthole"], "6.0 5.3 17.3": ["bullmastiff"], "4.8 14.9 17.6": ["perso"], "19.3 5.5 -0.3": ["pureplay"], "4.2 -6.4 -1.0": ["ipac"], "5.7 11.9 5.2": ["photostream"], "-3.7 27.0 9.5": ["accommodationist"], "9.9 17.9 18.2": ["photosynthesizing"], "18.7 9.8 14.9": ["skittery"], "-1.1 10.5 8.9": ["solitaires"], "7.5 5.9 17.2": ["luteolin"], "3.6 0.7 -0.7": ["pulvermedia"], "17.4 23.9 2.2": ["panopticon"], "1.7 14.7 1.9": ["saffronisation"], "12.1 10.0 11.6": ["usin"], "8.5 8.9 26.4": ["methoprene"], "7.7 15.3 14.5": ["ambiences"], "7.9 -0.7 35.6": ["pupu"], "0.7 -6.1 1.0": ["microdiscectomy"], "7.8 12.8 13.0": ["wincingly"], "11.6 15.4 9.3": ["urbanising"], "14.9 1.3 10.1": ["coinless"], "10.9 -1.5 -0.4": ["furnisher"], "11.7 27.2 21.0": ["handlines"], "7.1 7.2 9.0": ["microcells"], "9.6 6.3 6.1": ["contines"], "4.6 4.0 19.9": ["coolish"], "9.9 20.1 2.9": ["destablize"], "-6.2 8.8 11.7": ["posteason"], "4.9 1.1 8.4": ["resurgences"], "9.0 25.3 15.3": ["shmuck"], "12.9 23.0 12.7": ["curs"], "11.7 9.9 13.8": ["awk"], "15.2 5.0 14.2": ["glutting"], "18.0 6.0 27.4": ["gak"], "3.4 8.0 33.8": ["gratins"], "14.5 14.6 4.0": ["knuckledusters"], "-6.9 12.5 8.2": ["confluent"], "0.2 5.1 20.3": ["carmenere"], "-7.7 3.9 3.1": ["oxcarbazepine"], "5.9 1.7 2.5": ["multilink"], "7.9 6.0 11.3": ["lilts"], "6.7 6.5 29.4": ["flourless"], "11.5 9.1 12.0": ["heftily"], "-3.0 8.3 9.5": ["prodromal"], "2.9 0.7 2.7": ["matriculant"], "5.3 6.7 24.0": ["epicures"], "-0.2 7.8 5.4": ["neuroligin"], "4.9 21.2 10.7": ["gameness"], "1.6 6.5 10.8": ["multipotent"], "8.1 3.9 15.4": ["keepcase"], "2.9 5.2 1.5": ["headscarved"], "-0.4 6.4 5.1": ["immunostaining"], "6.3 12.8 26.3": ["reedbeds"], "8.1 7.8 17.9": ["tropically"], "11.4 15.2 19.9": ["sweety"], "8.1 5.3 16.2": ["noodly"], "-2.5 15.7 11.5": ["throughline"], "17.8 1.9 6.1": ["scaffolded"], "17.3 7.9 11.0": ["ologist"], "-2.2 7.7 1.0": ["penalisation"], "0.8 7.4 16.8": ["kerf"], "-0.2 8.8 14.0": ["methemoglobinemia"], "-2.3 15.6 6.4": ["excercising"], "13.6 -4.4 4.0": ["fran"], "-0.9 17.0 -0.7": ["encamp"], "3.2 12.9 -0.7": ["campiagn"], "-1.5 13.5 3.2": ["bikeable"], "9.8 -2.1 13.9": ["tilers"], "-1.5 2.5 6.2": ["lentiviral"], "8.6 5.7 9.5": ["pulchritudinous"], "17.7 8.7 12.7": ["treehuggers"], "4.8 5.9 -1.1": ["ution"], "-6.8 10.4 1.9": ["palyers"], "-5.7 13.7 0.6": ["urethritis"], "5.7 8.2 11.5": ["bohemianism"], "2.5 9.3 4.3": ["valuating"], "-7.6 -5.0 4.2": ["eached"], "-1.2 13.8 4.0": ["articulacy"], "16.7 39.1 11.9": ["teleporters"], "1.9 6.0 5.2": ["hygrometer"], "6.3 12.5 38.2": ["vaquita"], "10.9 3.8 17.1": ["crosier"], "12.9 36.7 16.5": ["minigun"], "9.6 12.5 9.6": ["proteasomes"], "6.0 9.2 20.2": ["wormer"], "1.4 6.3 2.3": ["illegibility"], "-1.4 6.7 6.0": ["infarctions"], "10.6 30.0 1.0": ["destablising"], "3.7 22.0 11.0": ["obeah"], "21.3 8.0 25.9": ["ichthyosaur"], "0.6 11.0 6.2": ["pollees"], "-4.4 6.5 11.5": ["firstplace"], "5.0 8.3 9.9": ["theanine"], "3.2 15.1 3.9": ["syndicalism"], "13.1 7.6 17.9": ["moated"], "1.0 2.1 15.1": ["aron"], "8.9 8.6 36.5": ["tideland"], "-0.7 19.1 0.3": ["preeminently"], "-6.8 6.4 4.5": ["phy"], "12.4 5.2 10.4": ["bafflegab"], "-0.6 9.3 17.0": ["dyan"], "18.4 21.6 10.4": ["befoul"], "7.2 5.0 17.4": ["dop"], "21.0 17.5 12.6": ["multisided"], "2.2 13.5 6.1": ["sanyasin"], "4.1 6.3 8.1": ["domaining"], "-5.6 -13.8 -3.0": ["recevied"], "-2.4 16.2 3.9": ["homeguard"], "3.4 9.6 17.1": ["tasseling"], "11.8 14.4 43.4": ["sargassum"], "13.5 18.6 14.0": ["nongamers"], "12.0 16.5 7.3": ["swearword"], "9.6 9.3 8.5": ["grimier"], "4.7 12.1 12.8": ["frivilous"], "6.5 13.2 -2.3": ["iterates"], "17.0 3.4 -3.2": ["wordmark"], "7.4 1.2 3.6": ["perviously"], "11.8 10.2 7.1": ["rememeber"], "10.1 7.0 8.1": ["hypertrophied"], "-1.9 20.3 8.4": ["deliberatively"], "-5.4 -1.9 6.4": ["thermoplasty"], "15.3 15.1 35.0": ["shoveler"], "14.1 2.4 19.6": ["bonemeal"], "-5.4 10.0 6.5": ["seconders"], "9.1 18.1 22.7": ["delicateness"], "4.2 8.0 17.5": ["plantsman"], "-0.2 3.8 3.6": ["bosutinib"], "5.1 5.5 17.7": ["zach"], "18.0 5.6 11.1": ["fellating"], "19.9 8.5 5.6": ["unbox"], "6.0 5.7 28.9": ["puris"], "16.7 16.9 20.1": ["chubbiness"], "6.8 5.2 13.7": ["shelterhouse"], "11.0 13.3 18.9": ["goosebump"], "8.0 7.6 27.0": ["repasts"], "4.0 10.1 7.1": ["daytrading"], "12.1 12.1 4.7": ["activitists"], "4.0 10.4 2.9": ["soem"], "-0.7 10.4 10.1": ["shor"], "10.1 10.6 4.5": ["troup"], "3.0 1.1 0.3": ["reservable"], "9.6 0.9 5.2": ["ofapproximately"], "4.5 3.8 20.0": ["grapey"], "3.5 -4.0 2.3": ["formore"], "-0.3 8.6 12.6": ["subtleness"], "9.3 7.1 11.0": ["fantasic"], "-0.4 5.7 2.7": ["latanoprost"], "8.1 5.5 10.7": ["strummers"], "4.8 11.7 8.1": ["daunts"], "5.0 8.7 7.8": ["aluminized"], "-7.1 4.5 11.8": ["thow"], "5.4 12.5 10.2": ["combis"], "8.0 -1.3 -0.3": ["feasability"], "21.3 10.8 9.9": ["panjandrums"], "6.5 6.4 3.9": ["lc"], "10.3 12.7 19.2": ["nassau"], "7.8 0.6 9.0": ["andmore"], "3.5 -2.2 7.5": ["racewear"], "12.4 21.0 20.5": ["feets"], "17.0 14.1 17.5": ["awayday"], "2.7 2.6 3.8": ["carseats"], "13.1 13.1 11.9": ["illusionistic"], "7.1 7.6 31.4": ["ramin"], "11.8 13.3 10.3": ["offstump"], "6.9 5.1 19.8": ["biscuity"], "9.7 12.9 38.7": ["buffleheads"], "7.9 -3.8 4.7": ["leadless"], "5.1 2.3 17.5": ["periosteum"], "8.5 10.9 11.0": ["roun"], "5.5 6.8 35.4": ["shearwater"], "-1.5 6.4 3.3": ["lection"], "-1.8 6.8 2.3": ["rilonacept"], "8.5 12.6 7.1": ["illuminance"], "-1.8 12.6 5.3": ["prepaids"], "2.5 -5.4 -0.6": ["radiochemistry"], "2.6 6.6 10.4": ["reverser"], "15.3 2.8 12.5": ["sexpots"], "-1.3 -3.6 0.7": ["hald"], "9.1 15.1 9.1": ["owt"], "-1.4 16.0 9.3": ["becoz"], "4.4 29.1 -4.0": ["assasinate"], "21.8 3.1 15.4": ["extrudes"], "2.2 17.0 5.1": ["mohammed"], "2.1 -1.8 15.5": ["sheanut"], "1.3 14.2 14.1": ["incredibility"], "4.9 6.7 29.3": ["forebay"], "-1.6 -6.5 15.8": ["commis"], "18.7 9.8 13.7": ["clomp"], "13.2 9.9 1.1": ["masers"], "15.2 15.1 9.4": ["glitched"], "7.6 5.6 16.2": ["rockies"], "-0.3 8.5 7.1": ["nonconformance"], "0.4 18.4 14.8": ["onsides"], "6.4 24.1 11.3": ["innoculated"], "1.6 11.7 3.8": ["neeed"], "-0.6 1.9 6.4": ["mimetics"], "8.5 22.1 1.4": ["amnesiacs"], "2.3 14.0 0.3": ["misdoing"], "16.2 7.0 13.4": ["shaked"], "2.6 21.9 12.5": ["bullshitter"], "-8.1 11.7 4.0": ["hyperopia"], "-7.7 6.4 12.5": ["neurotrophins"], "15.9 9.4 14.9": ["fluffer"], "5.9 -3.2 3.2": ["cogen"], "6.0 11.2 1.0": ["mischievious"], "5.8 5.4 13.1": ["phosphatic"], "4.3 -1.4 -4.9": ["chauffered"], "-4.5 17.9 -0.4": ["misreadings"], "7.9 25.2 5.1": ["punishers"], "7.2 14.9 16.9": ["newtons"], "1.6 8.7 16.3": ["portsmouth"], "13.2 5.7 2.0": ["profitablity"], "16.8 9.9 12.3": ["pigskins"], "14.4 7.1 11.3": ["ampitheatre"], "4.8 15.1 9.1": ["direr"], "6.4 17.2 14.8": ["counterpiracy"], "7.8 16.6 9.0": ["spunkiness"], "5.6 -1.4 1.8": ["thefinancial"], "6.8 1.0 9.4": ["petrographic"], "13.8 13.3 12.7": ["ocracy"], "15.3 13.1 7.9": ["nouse"], "-1.2 25.7 17.1": ["somtimes"], "-2.6 7.9 9.5": ["famiy"], "3.5 5.3 9.5": ["springfield"], "5.6 14.8 12.2": ["sordidness"], "-1.0 8.0 6.1": ["gues"], "5.9 0.3 14.1": ["lori"], "10.1 5.0 5.3": ["unforgetable"], "0.7 15.0 11.4": ["primitivist"], "3.6 22.0 -6.0": ["allegience"], "13.7 6.3 1.6": ["trendspotting"], "2.5 6.4 11.0": ["midweeks"], "5.5 9.2 11.5": ["palletised"], "9.5 16.4 11.1": ["cognates"], "2.6 -1.9 3.2": ["compatibles"], "3.5 4.3 1.6": ["digitiser"], "-1.4 17.3 1.8": ["contesters"], "2.3 9.6 0.3": ["pitot"], "11.0 15.3 9.2": ["overcapacities"], "-0.7 25.4 7.1": ["inflationist"], "-12.5 1.7 8.0": ["aquainted"], "2.5 17.0 9.2": ["physicaled"], "6.5 18.7 2.8": ["supplicating"], "1.3 10.7 9.9": ["decarbonization"], "0.5 13.0 7.4": ["patronymic"], "-7.8 8.8 7.8": ["wardrobing"], "1.2 8.4 17.8": ["melismatic"], "-3.1 2.3 6.3": ["nonhormonal"], "2.3 -2.0 -1.1": ["commun"], "12.1 0.3 19.5": ["crumby"], "-8.0 10.5 11.2": ["patrilineal"], "18.2 9.9 14.0": ["wheelings"], "-4.8 5.2 14.0": ["digestate"], "-1.5 7.6 16.4": ["pamilya"], "10.6 8.0 7.2": ["outdraws"], "-0.2 0.9 4.9": ["asf"], "3.6 8.5 15.4": ["hydrography"], "13.7 2.7 10.3": ["nattily"], "13.0 14.5 26.1": ["crosshatched"], "2.5 3.5 0.0": ["antiracism"], "0.3 7.6 10.7": ["crossfade"], "10.9 7.3 28.2": ["beachings"], "6.5 0.1 3.4": ["contin"], "8.9 7.7 17.5": ["intermedia"], "17.5 11.7 18.7": ["overgrowing"], "9.0 8.7 8.6": ["ciboodle"], "11.7 13.8 12.9": ["darkie"], "15.4 10.7 26.2": ["whipper"], "10.6 10.1 8.5": ["subbasement"], "5.5 8.8 0.7": ["nonclassified"], "11.1 11.0 11.4": ["sketchiness"], "10.4 14.4 7.6": ["outting"], "3.8 14.5 11.9": ["arterioles"], "6.4 6.9 17.5": ["pallette"], "1.4 5.2 37.8": ["zeppoles"], "14.9 2.7 2.2": ["widescreens"], "0.0 14.3 11.5": ["precancers"], "5.7 8.5 4.9": ["beltless"], "12.3 12.7 22.1": ["parafoil"], "10.7 0.2 21.0": ["shirred"], "8.1 16.2 10.3": ["speciously"], "-1.6 12.7 9.8": ["undrivable"], "14.6 7.4 5.4": ["fcuk"], "-4.1 15.7 -1.1": ["differnet"], "18.3 20.1 12.6": ["chupacabras"], "4.9 2.9 5.3": ["bima"], "9.0 -0.7 3.8": ["ispo"], "5.6 3.9 8.0": ["chelators"], "7.7 13.1 11.2": ["felicitously"], "15.7 9.5 38.6": ["jimmies"], "8.0 24.8 8.6": ["autorotation"], "1.0 8.8 15.6": ["understocked"], "4.8 2.9 10.2": ["premiumization"], "17.9 6.7 12.6": ["groover"], "8.6 11.9 17.4": ["cena"], "11.1 13.4 16.2": ["dunnage"], "2.0 4.4 10.4": ["subdudes"], "14.5 15.3 8.6": ["escapology"], "10.4 -0.4 -3.1": ["synchrotrons"], "11.8 3.4 16.3": ["boinking"], "3.9 11.7 5.6": ["seratonin"], "2.0 13.7 0.2": ["alterable"], "8.0 4.6 20.4": ["waterscapes"], "16.6 7.2 31.2": ["beefsteaks"], "4.8 8.7 2.9": ["canonise"], "10.1 6.9 7.5": ["kodak"], "7.5 -2.6 8.5": ["folkster"], "-4.3 6.6 2.9": ["capacitances"], "-1.6 -1.0 12.6": ["kumu"], "6.7 0.9 19.6": ["waterflow"], "13.0 4.0 6.9": ["attendent"], "-0.1 -3.8 7.7": ["cashouts"], "9.0 11.6 10.0": ["stepless"], "1.0 9.4 9.1": ["nondiversified"], "1.6 12.9 8.0": ["papabile"], "3.5 12.7 7.6": ["unsaddled"], "6.9 2.2 14.0": ["weighers"], "10.4 19.1 15.9": ["autogyro"], "13.4 12.0 12.6": ["waxer"], "25.3 23.7 37.5": ["bluebottles"], "-2.6 25.8 5.3": ["sargeant"], "0.8 0.7 3.9": ["suppor"], "4.0 8.4 14.7": ["snicks"], "7.0 11.4 13.2": ["doorkeepers"], "5.2 4.4 9.6": ["mul"], "20.9 14.4 12.3": ["spoofers"], "5.8 12.7 15.1": ["whitebread"], "-1.7 6.5 9.7": ["lendable"], "-2.6 2.1 9.8": ["tained"], "-1.7 12.5 8.3": ["pary"], "-0.0 5.9 4.8": ["reponses"], "8.2 1.8 8.8": ["playcentre"], "4.4 17.8 1.5": ["sonorously"], "-6.5 5.0 4.6": ["hornist"], "8.3 7.7 32.7": ["poori"], "14.5 -0.6 -2.8": ["theart"], "17.9 11.2 27.2": ["plumbago"], "7.9 -4.3 3.1": ["sthe"], "2.1 1.6 4.4": ["commissaire"], "-5.8 13.6 7.6": ["gluconeogenesis"], "3.4 8.9 12.6": ["lage"], "1.9 5.9 -1.4": ["bivalent"], "8.3 -1.3 14.4": ["inelasticity"], "3.1 2.3 18.6": ["mora"], "8.6 13.8 2.3": ["yellers"], "18.8 21.1 14.6": ["hellcat"], "1.9 7.5 5.9": ["collabs"], "7.8 10.6 12.0": ["happoshu"], "11.4 -0.7 11.4": ["gia"], "-11.4 -6.4 -8.3": ["saidd"], "16.2 12.8 11.7": ["bargin"], "0.6 15.0 3.8": ["suasion"], "14.4 8.8 7.0": ["treo"], "10.5 3.6 45.2": ["brandade"], "20.6 15.9 14.0": ["friggen"], "5.7 5.1 12.3": ["botton"], "1.6 12.3 11.0": ["pleasanter"], "0.6 18.6 -1.0": ["reproving"], "15.6 19.7 14.2": ["oppositely"], "0.2 5.4 7.1": ["aas"], "2.4 0.9 5.2": ["ytterbium"], "4.9 13.2 8.9": ["evan"], "5.8 21.1 10.2": ["mavericky"], "3.4 -4.4 10.0": ["defrays"], "7.5 3.5 17.4": ["gothy"], "8.3 3.9 5.0": ["aready"], "21.5 11.0 15.5": ["glueing"], "4.8 12.6 0.2": ["obtrusively"], "-6.1 2.3 5.1": ["tapeouts"], "9.6 4.0 10.8": ["hyuk"], "2.0 1.6 8.7": ["colourists"], "-3.0 8.6 23.2": ["swards"], "-7.8 0.6 0.1": ["adenotonsillectomy"], "12.2 10.4 -2.5": ["itwould"], "2.9 4.4 13.3": ["baul"], "4.2 3.0 11.6": ["parfum"], "11.4 2.5 14.8": ["avoirdupois"], "5.2 13.0 15.2": ["asexually"], "-1.9 7.5 7.8": ["statemate"], "5.1 16.4 5.7": ["premonitory"], "1.1 10.1 8.4": ["endostatin"], "8.9 2.2 20.1": ["whitens"], "-4.3 8.2 11.6": ["walkups"], "0.3 4.7 14.5": ["rito"], "16.4 15.2 36.4": ["okonomiyaki"], "8.5 11.2 19.1": ["microbeads"], "-3.1 16.3 6.7": ["observability"], "-1.1 3.3 38.1": ["triploids"], "4.4 13.5 3.9": ["diametric"], "2.6 22.2 6.1": ["tabun"], "23.7 13.6 15.1": ["rolly"], "9.0 6.7 25.6": ["ageratum"], "-5.9 1.9 12.5": ["nonelection"], "17.6 18.3 18.1": ["ordure"], "-1.5 8.3 1.5": ["cilostazol", "welfares"], "-1.9 4.8 9.1": ["seocnd"], "0.4 3.6 5.7": ["ofthese"], "5.2 8.3 10.8": ["einige"], "7.7 -2.1 12.3": ["opry"], "10.2 11.8 15.0": ["salinization"], "-5.9 1.6 2.7": ["exerciseable"], "-1.3 11.0 6.1": ["zestfully"], "6.4 9.8 12.3": ["sirf"], "6.7 13.3 14.1": ["fratboy"], "5.0 8.5 9.0": ["lipopolysaccharide"], "-0.5 5.0 3.0": ["curial"], "4.3 19.7 15.6": ["coolheaded"], "11.6 22.7 14.2": ["sledger"], "-3.4 5.0 7.2": ["chasidic"], "6.9 14.8 6.3": ["freemarket"], "2.7 23.4 8.7": ["supernaturalism"], "-1.1 13.0 14.6": ["overconcentration"], "13.3 23.7 17.8": ["enziguiri"], "8.6 27.2 19.9": ["phytochrome"], "7.2 10.1 15.5": ["downtube"], "11.8 15.0 21.4": ["phalanges"], "4.5 10.7 11.0": ["lowriding"], "-2.3 9.3 1.6": ["bannings"], "-0.6 -1.9 10.6": ["dyn"], "-15.6 -3.0 -2.2": ["rehospitalized"], "19.3 16.9 23.5": ["gibbet"], "7.3 13.3 12.1": ["ustedes"], "11.6 2.6 9.9": ["bogland"], "1.4 20.5 5.5": ["ilm"], "11.0 14.0 18.4": ["pestles"], "-4.3 7.2 -1.3": ["nonbiased"], "8.4 9.1 3.3": ["screengrabs"], "2.0 -3.1 4.5": ["perfomers"], "-3.8 10.0 3.4": ["amrubicin"], "0.4 8.5 7.5": ["droving"], "-9.0 11.2 1.4": ["reintervention"], "4.4 19.4 4.8": ["sickbay"], "14.5 7.9 -3.7": ["solus"], "13.7 13.7 11.5": ["linespeople"], "10.0 3.2 12.9": ["glams"], "-1.0 12.9 12.0": ["stilll"], "6.2 4.5 18.6": ["likkle"], "9.1 12.8 13.0": ["grasscourts"], "1.0 6.9 8.1": ["lidlifter"], "-6.0 5.3 12.9": ["dian"], "2.2 21.1 5.6": ["prayin"], "4.9 14.3 11.1": ["sanchez"], "0.7 9.5 8.1": ["prepossessing"], "-6.3 10.6 5.1": ["recusing"], "7.2 11.8 19.0": ["rareness"], "14.8 5.4 25.8": ["pide"], "5.3 9.6 -0.9": ["denationalization"], "13.7 13.3 22.7": ["pitons"], "3.0 6.4 20.3": ["sandier"], "3.1 7.8 17.6": ["harrison"], "4.0 -0.3 12.5": ["vesicular"], "10.5 10.0 37.2": ["calicos"], "-2.6 5.5 14.9": ["korero"], "4.5 0.2 0.7": ["jours"], "4.3 4.9 9.8": ["subpostmasters"], "4.8 12.0 21.8": ["nonkosher"], "0.7 13.8 5.5": ["expurgated"], "13.5 20.5 10.7": ["malinvestments"], "11.2 8.1 6.5": ["forcasts"], "15.2 4.1 23.9": ["concretions"], "15.0 -0.5 1.8": ["annoucned"], "-3.2 4.6 5.5": ["dapsone"], "1.4 18.8 19.6": ["waterhemp"], "3.5 25.1 14.8": ["battlewagons"], "9.5 11.9 12.1": ["pikey"], "29.7 29.5 32.0": ["wabbit"], "15.3 39.2 10.7": ["magics"], "14.2 13.5 19.3": ["blackthorn"], "9.0 13.1 6.9": ["nanoworld"], "5.1 4.4 5.5": ["quelques", "bve"], "5.6 9.3 9.4": ["burqini"], "2.8 17.1 15.7": ["philosophizes"], "-0.3 1.0 12.4": ["benfit"], "6.9 5.0 17.1": ["granolas"], "6.8 6.5 15.4": ["jao"], "15.0 4.6 10.2": ["biocatalyst"], "5.2 17.1 17.3": ["effeminacy"], "-0.4 6.7 9.6": ["folksingers"], "6.4 -1.1 6.9": ["offtaker"], "17.9 10.0 21.7": ["dessicated"], "11.2 10.3 10.9": ["footsore"], "-12.2 7.1 8.9": ["legislatives"], "3.2 8.4 15.5": ["braininess"], "0.1 2.0 5.7": ["acetates"], "13.0 9.5 17.3": ["malling"], "8.0 9.8 16.9": ["richmond"], "-0.6 3.0 7.6": ["eprotirome"], "16.4 7.7 8.5": ["navratnas"], "11.2 12.1 22.7": ["retsina"], "20.6 12.9 20.3": ["hummocks"], "17.0 -2.7 13.4": ["multiregional"], "1.8 15.1 9.1": ["dumpoffs"], "7.5 16.5 6.8": ["hoofbeats"], "17.8 15.2 13.5": ["butthead"], "10.2 10.2 8.4": ["umlauts"], "-3.2 7.7 3.2": ["personalty"], "6.1 0.3 12.4": ["delaware"], "-1.6 21.4 6.8": ["effacing"], "3.9 13.5 -3.4": ["apalling"], "-6.5 11.0 3.2": ["chowks"], "4.6 6.0 27.5": ["saag"], "6.1 8.4 18.8": ["slobby"], "1.7 3.0 11.9": ["homa"], "4.0 8.0 8.7": ["steading"], "15.8 31.8 17.1": ["recolonise"], "5.7 7.9 14.7": ["logan"], "-1.1 7.1 -1.5": ["therapeutical"], "-8.1 6.2 7.4": ["criterias"], "6.6 10.9 29.6": ["outport"], "8.2 1.5 2.2": ["serivce"], "18.5 7.8 33.3": ["feedbag"], "-1.1 26.9 5.4": ["undefendable"], "-6.2 11.2 21.6": ["pono"], "-4.4 1.8 10.1": ["biostatistical"], "9.2 8.3 7.5": ["ingestions"], "4.9 15.1 0.8": ["mousesports"], "-4.7 4.8 -1.4": ["convoking"], "9.1 3.8 16.8": ["fal"], "0.7 12.9 8.6": ["thrombi"], "12.4 9.6 34.2": ["midwater"], "7.3 9.4 6.3": ["quadband"], "4.0 6.8 14.1": ["maiko"], "-4.6 -0.5 2.9": ["eptifibatide"], "1.8 15.6 2.0": ["sterotypes"], "-2.9 15.5 3.9": ["eyeopener"], "5.7 1.8 6.3": ["glibc"], "3.8 5.9 5.3": ["mots"], "10.7 10.5 5.9": ["uncombed"], "6.0 6.8 10.5": ["honkytonk"], "8.0 -2.1 0.4": ["reaudit"], "7.2 9.7 21.4": ["peccary"], "-7.9 8.4 5.7": ["agunot"], "23.6 10.3 18.7": ["snuggie"], "0.6 1.4 1.2": ["flexibilty"], "17.6 5.0 25.1": ["cheerios"], "-3.5 1.0 14.7": ["zardosi"], "15.6 9.1 27.7": ["dishtowel"], "10.2 19.3 4.8": ["symbologist"], "3.2 9.4 8.6": ["femalefirst"], "5.1 18.6 8.8": ["eternities"], "11.2 3.3 23.3": ["lacquering"], "10.1 17.8 19.2": ["verdure"], "5.8 1.9 18.5": ["kif"], "6.4 10.3 20.6": ["fipronil"], "3.2 15.7 16.2": ["plateaux"], "-4.0 -6.1 6.6": ["calver"], "-4.3 11.2 7.8": ["linesmaker"], "22.1 6.7 13.2": ["cloner"], "-1.9 11.4 4.8": ["qualies"], "9.0 11.6 -0.4": ["egyptian"], "12.1 7.3 4.4": ["bioproduction"], "1.8 1.5 14.9": ["rowhomes"], "3.8 1.5 -0.0": ["cataloguer"], "-0.7 1.1 -0.1": ["avialable"], "9.8 -5.5 7.5": ["upcomming"], "20.5 10.9 13.9": ["unscrews"], "6.8 17.5 15.8": ["pointspreads"], "13.8 13.3 8.5": ["turks"], "9.5 18.6 7.2": ["pooler"], "2.9 8.8 17.9": ["irie"], "12.7 9.5 4.3": ["shabbiest"], "2.2 3.6 1.2": ["excusive"], "-4.5 7.2 -1.1": ["sufferred"], "3.3 3.6 22.6": ["dishtowels"], "0.6 34.5 0.2": ["civillian"], "0.9 9.4 0.7": ["urdu"], "3.1 20.7 8.5": ["solidarities"], "12.3 4.0 5.8": ["electrostatics"], "3.8 21.9 4.3": ["autopen"], "18.5 6.1 32.9": ["sandwhich"], "9.8 8.8 20.0": ["narcissi"], "7.4 17.3 3.5": ["peerlessly"], "3.5 0.1 3.2": ["cincinnati"], "0.2 6.1 15.4": ["sedar"], "-6.7 21.1 1.5": ["interpersonally"], "12.8 11.2 5.2": ["airshaft"], "3.6 8.3 7.8": ["geocode"], "10.0 8.4 10.9": ["piccolos"], "-0.2 9.5 9.1": ["arenavirus"], "0.9 24.0 6.1": ["civ"], "-1.1 7.0 6.6": ["oneway"], "0.4 15.4 8.2": ["centromeres"], "16.5 12.1 3.8": ["glamourising"], "-9.0 0.2 -3.1": ["empanelling"], "4.0 18.3 7.5": ["maan"], "19.3 13.8 12.3": ["mazing"], "10.2 16.4 0.7": ["drudges"], "3.8 4.4 -0.0": ["augmentative"], "1.2 15.6 10.1": ["underclothing"], "1.5 -2.5 11.0": ["bijoux"], "-4.6 3.8 8.8": ["countertenors"], "3.5 11.5 14.7": ["fpga"], "6.2 6.2 9.7": ["tracy"], "-2.9 12.7 2.7": ["remobilization"], "2.8 14.5 0.8": ["individuated"], "11.9 15.0 4.5": ["diseconomies"], "5.2 14.4 7.4": ["nonesense"], "4.6 -14.0 9.9": ["retendered"], "14.6 7.4 23.3": ["churrascaria"], "3.7 11.7 -1.6": ["stra"], "11.6 17.7 11.3": ["mentalism"], "29.6 10.1 23.1": ["snarfing"], "-2.4 12.0 7.9": ["upregulate"], "1.7 11.4 12.8": ["eary"], "6.1 4.6 0.9": ["reposts"], "13.8 5.9 17.2": ["superlong"], "16.2 17.4 9.2": ["spazzed"], "-0.3 4.5 12.4": ["flocculation"], "1.2 20.9 8.9": ["throughways"], "20.1 6.8 29.7": ["sherbert"], "2.3 10.0 3.4": ["vijay"], "5.2 18.0 8.4": ["pitiably"], "9.0 -0.1 11.2": ["thea"], "7.7 14.3 25.7": ["hardpack"], "11.8 9.3 44.6": ["mudbugs"], "5.2 17.8 3.6": ["unshod"], "-3.7 6.8 3.1": ["dextroamphetamine"], "4.4 13.4 9.1": ["overserving"], "6.5 -0.4 -1.2": ["interm"], "8.8 16.2 15.4": ["etymologically"], "4.0 6.2 10.1": ["biogeochemist"], "-0.5 3.2 10.9": ["piaffe"], "-7.0 -3.5 -0.2": ["anincrease"], "10.0 16.8 8.3": ["claycourter"], "9.3 7.6 19.6": ["tenpin"], "-3.2 0.1 -4.6": ["confernece"], "18.1 15.3 4.5": ["unloosed"], "16.6 15.2 19.8": ["goldilocks"], "15.0 13.5 13.1": ["flimsily"], "15.8 5.2 12.8": ["sealink"], "12.2 17.7 20.9": ["fencerow"], "11.0 14.0 8.0": ["moded"], "-0.9 11.8 16.4": ["henderson"], "20.1 20.6 24.3": ["sparrowhawk"], "13.3 11.8 16.5": ["friskiness"], "14.2 16.5 16.7": ["escutcheon"], "11.3 7.8 11.1": ["incise"], "0.8 4.5 5.4": ["iconographer"], "6.7 16.1 10.6": ["donga"], "0.7 6.1 35.9": ["sinigang"], "-7.5 3.4 4.3": ["administratrix"], "13.7 6.5 13.0": ["upand"], "8.2 1.3 12.2": ["obs"], "2.1 15.4 6.7": ["freezeproof"], "2.1 -3.4 12.5": ["lakecity"], "10.2 8.8 7.3": ["presente"], "7.1 8.2 12.9": ["expediters"], "11.2 7.3 12.4": ["wayfaring"], "10.1 15.5 7.0": ["starfield"], "2.7 0.6 2.3": ["englisch"], "11.3 2.3 3.6": ["touchpanels"], "7.4 2.3 23.7": ["overbaked"], "5.4 6.5 14.1": ["ycombinator"], "0.3 16.8 17.1": ["cullers"], "5.0 7.5 17.2": ["joan"], "4.9 7.0 10.1": ["tinkerings"], "2.3 6.0 2.5": ["herstory"], "-6.6 11.3 3.7": ["expatiate"], "15.4 15.7 12.1": ["fakirs"], "2.4 4.1 3.1": ["functionalist"], "8.4 20.7 9.9": ["brane"], "-2.5 -0.7 1.2": ["schol"], "-2.2 13.0 -1.5": ["interprete"], "-11.5 -3.4 5.2": ["catheterized"], "7.7 8.6 5.9": ["sidearming"], "11.2 7.7 8.5": ["rainproof"], "-2.5 21.3 14.1": ["respec"], "9.2 2.1 9.2": ["opoly"], "4.0 6.9 18.8": ["tuneage"], "-2.7 8.4 6.2": ["unsoundness"], "-2.8 11.1 12.7": ["raggedness"], "-1.2 4.7 5.4": ["shiftwork"], "6.8 19.3 19.7": ["abeam"], "4.9 22.6 19.9": ["reticles"], "4.0 -0.9 26.6": ["sangrias"], "6.9 2.8 4.2": ["accessorizes"], "12.5 6.9 8.4": ["clr"], "15.3 19.7 33.4": ["hellbender"], "-1.3 3.2 15.3": ["superfectas"], "5.1 4.5 9.1": ["clef"], "2.8 9.3 4.8": ["ejaculatory"], "7.3 11.1 6.9": ["alkalines"], "-2.9 15.6 6.1": ["dovishness"], "2.8 7.9 16.9": ["jins"], "0.2 3.5 8.1": ["pci"], "9.7 8.3 -1.5": ["andin"], "5.0 7.4 9.0": ["argillic"], "5.6 12.4 6.0": ["pronounciation"], "23.0 6.7 15.5": ["pattered"], "23.3 6.7 13.8": ["drowsily"], "8.0 17.1 21.7": ["parch"], "1.5 12.2 -5.3": ["joip"], "21.1 9.2 7.2": ["costcutting"], "3.2 1.4 4.7": ["microdosing"], "7.8 2.0 28.7": ["neeps"], "-2.2 0.2 5.8": ["biospecimens"], "2.0 6.3 8.5": ["graveling"], "2.6 4.4 5.3": ["enfant"], "7.7 4.1 5.4": ["moneysupermarket"], "12.4 19.0 17.2": ["alchemic"], "6.2 10.3 4.1": ["clutchless"], "4.2 7.4 12.2": ["counterpointed"], "9.6 4.6 14.8": ["healty"], "-7.8 1.3 -1.7": ["intubations"], "2.1 6.3 5.6": ["tractability"], "-1.1 12.2 20.9": ["agarwood"], "20.6 12.3 14.7": ["pawprints"], "1.7 -8.9 14.0": ["nual"], "13.2 19.7 9.3": ["blockheaded"], "-1.7 3.7 11.0": ["iu"], "13.8 6.0 2.5": ["microdevices"], "6.6 -0.0 9.5": ["ineedhits"], "7.7 10.4 15.1": ["unhealthiness"], "7.4 7.2 13.4": ["zedonk"], "4.0 8.3 18.1": ["inseminating"], "3.9 11.8 28.2": ["cucurbits"], "18.0 4.5 12.2": ["charango"], "5.6 3.4 5.5": ["atheroma"], "6.9 13.2 14.2": ["foliation"], "-4.9 18.0 1.1": ["patronisation"], "2.3 6.5 6.7": ["successfulness"], "9.0 -0.6 2.0": ["refurbishers"], "13.7 3.6 22.6": ["tombolas"], "11.1 19.1 6.5": ["gunshy"], "2.6 -0.1 14.8": ["laffers"], "-7.2 20.2 4.3": ["derogating"], "0.1 20.9 6.9": ["extraconstitutional"], "5.1 13.1 11.5": ["marestail"], "-1.2 6.8 6.9": ["dramde"], "0.6 13.8 16.7": ["ponded"], "1.7 -2.5 23.9": ["compostables"], "3.7 7.9 28.5": ["muskmelon"], "16.9 6.9 4.6": ["silverlight"], "1.4 17.5 7.7": ["direness"], "3.7 7.8 12.3": ["secondrow"], "7.2 2.0 10.6": ["zz"], "16.0 5.0 14.2": ["torero"], "10.3 17.2 22.4": ["zephyrs"], "8.2 3.3 12.4": ["inot"], "17.5 10.4 24.6": ["slurpy"], "12.8 7.7 9.7": ["gimping"], "0.8 15.9 9.6": ["salat"], "-1.8 -4.7 8.5": ["bswift"], "4.4 2.7 15.2": ["decimalization"], "1.6 12.6 15.2": ["andhra"], "-1.1 18.5 4.3": ["interrupters"], "8.0 1.7 8.9": ["creditcard"], "0.4 10.6 12.1": ["gwaan"], "10.1 -2.0 15.5": ["drywaller"], "20.0 9.2 15.8": ["shiney"], "8.7 8.6 5.3": ["hymnbook"], "-2.5 0.0 14.7": ["lobular"], "19.6 14.1 6.4": ["longheld"], "14.4 7.4 9.0": ["avtaar"], "11.1 14.2 9.1": ["microcephalic"], "6.2 20.2 10.7": ["irrationalism"], "9.7 0.8 15.9": ["fendered"], "20.4 22.4 12.1": ["fanboi"], "10.9 -2.2 -5.6": ["revelaed"], "10.2 12.7 6.4": ["slaphappy"], "0.3 10.1 16.6": ["campier"], "-3.0 2.2 12.7": ["inoculants"], "10.8 4.9 12.2": ["etcher"], "-3.2 10.2 9.1": ["palpate"], "3.0 7.1 10.9": ["cadenced"], "-8.5 -2.1 5.0": ["posttreatment"], "8.9 2.1 -1.4": ["silex"], "7.2 12.0 11.5": ["reclamations"], "5.7 1.0 0.7": ["prepurchase"], "-0.6 2.6 4.8": ["pto"], "3.5 15.6 4.4": ["extrications"], "16.2 10.5 24.9": ["twinkies"], "8.2 25.0 6.1": ["patroled"], "10.1 1.0 14.3": ["doble"], "6.8 -2.2 15.7": ["boding"], "2.2 10.2 6.5": ["pentecostal"], "4.1 -2.5 -2.1": ["technikons"], "8.5 9.8 24.0": ["chokeberry"], "14.0 5.3 41.3": ["haloumi"], "6.5 8.7 16.8": ["trishaws"], "10.1 14.7 6.6": ["schmoe"], "16.5 7.4 12.6": ["abnormals"], "14.0 13.8 15.0": ["nerved"], "5.2 19.3 19.5": ["blackjacks"], "12.6 22.3 4.6": ["latently"], "5.9 9.9 7.8": ["spaciously"], "9.6 2.0 32.8": ["kalbi"], "-1.0 3.0 6.4": ["increse"], "8.6 12.7 17.5": ["kikuyu"], "-2.7 4.5 11.4": ["mashgiach"], "-2.8 9.0 -1.2": ["arbitrable"], "20.2 23.8 19.0": ["broadswords"], "6.8 9.1 2.2": ["homeshoring"], "10.2 2.7 29.9": ["poppyseed"], "1.1 17.5 -4.2": ["ynet"], "-3.4 9.5 27.0": ["aperitivo"], "4.5 11.3 7.5": ["releif"], "15.0 9.9 6.0": ["undented"], "3.0 21.4 11.5": ["existentialists"], "15.5 12.3 11.4": ["netscape"], "10.4 0.9 14.8": ["bagpiping"], "4.6 7.9 8.7": ["circumambulation"], "2.2 9.9 6.0": ["cocknfire"], "7.2 9.9 14.2": ["butalbital"], "9.3 12.8 11.0": ["mantrip", "outstretch"], "-1.1 12.5 25.6": ["biotoxin"], "3.4 15.7 12.0": ["jal"], "11.8 8.2 5.4": ["megajoules"], "2.5 6.3 0.8": ["interwove"], "3.0 19.6 2.5": ["institutionalism"], "0.1 17.6 10.2": ["cosplayer"], "19.7 19.0 23.0": ["chessmen"], "20.2 10.1 25.3": ["twinkie"], "-2.6 16.5 4.8": ["favorited"], "-8.2 22.5 -4.4": ["equivocates"], "-1.5 2.9 14.3": ["deferoxamine"], "6.0 1.6 8.9": ["tucson"], "12.5 12.3 1.2": ["undermanaged"], "9.6 5.2 8.9": ["toal"], "-7.9 14.8 2.3": ["vaccinees"], "12.0 4.8 11.3": ["nonproducing"], "14.0 7.2 35.9": ["molts"], "15.0 18.2 2.3": ["irremovable"], "-3.4 3.3 -2.8": ["paraplanning"], "11.0 -1.0 0.9": ["addl"], "-2.0 10.0 18.4": ["exudates"], "11.0 8.2 10.9": ["skygazers"], "0.9 -2.6 5.8": ["refixed"], "0.1 11.6 4.6": ["fulfillments"], "6.7 10.6 48.6": ["makos"], "-2.0 6.2 5.0": ["encryptors"], "0.8 3.6 16.1": ["rosarian"], "-2.8 13.7 2.8": ["grievers"], "11.5 5.8 33.8": ["bateau"], "12.1 23.6 9.3": ["delusive"], "18.9 3.5 -1.3": ["manufactuers"], "-0.3 -3.2 6.8": ["prbuzz"], "5.7 -9.8 -0.9": ["inlcudes"], "11.0 8.6 30.0": ["epicureans"], "8.0 11.7 7.6": ["kookie"], "9.8 6.8 36.3": ["banh"], "15.6 -5.3 18.7": ["hefts"], "1.1 7.2 -2.0": ["literacies"], "1.0 19.4 3.5": ["outshoots"], "-6.8 -1.7 5.3": ["lactulose"], "3.7 -5.0 -7.1": ["outdoored"], "2.0 4.0 -1.0": ["detikcom"], "16.6 8.4 3.1": ["lobotomised"], "8.8 13.3 19.7": ["coevolution"], "3.8 8.1 2.0": ["derivable"], "-1.4 4.7 8.0": ["footbeds"], "0.4 2.0 19.2": ["doublehanded"], "-7.5 16.6 3.2": ["whome"], "8.2 4.9 8.3": ["thinspiration"], "22.3 4.9 36.5": ["mongo"], "5.1 15.1 5.8": ["chondrules"], "0.2 2.8 22.2": ["aldicarb"], "10.8 5.0 17.7": ["cobwebby"], "1.4 40.6 16.1": ["respawns"], "3.0 9.5 20.7": ["leggies"], "8.2 9.2 5.3": ["lexicography"], "2.0 20.3 2.3": ["unreciprocated"], "19.1 20.4 13.9": ["pestilent"], "11.5 10.9 10.3": ["macromolecule"], "9.5 21.7 20.0": ["foulness"], "-5.0 13.3 5.6": ["kgosi"], "12.9 2.4 45.4": ["unshelled"], "3.9 6.3 8.3": ["resistin"], "-1.8 11.5 1.0": ["revelator"], "-0.1 1.1 11.9": ["fumonisin"], "17.4 4.8 21.9": ["funfairs"], "7.1 24.1 6.4": ["envelopment"], "14.6 20.1 6.0": ["unsearchable"], "-2.0 17.8 4.7": ["misallocations"], "12.5 22.9 13.2": ["unrecognizably"], "8.7 5.3 7.0": ["prompters"], "9.9 21.7 1.4": ["needto"], "11.2 8.0 1.3": ["vaunt"], "8.6 -3.4 11.8": ["zay"], "1.2 13.1 13.3": ["screwjob"], "17.1 10.6 2.1": ["multicountry"], "-1.7 8.0 7.1": ["trafficway"], "7.0 18.8 11.2": ["exhaustible"], "7.3 4.5 2.9": ["lessthan"], "9.4 -2.6 15.8": ["dugs"], "5.8 6.8 26.9": ["payasam"], "-6.6 -0.0 5.7": ["nonpeak"], "4.2 4.7 11.9": ["datas"], "-1.6 5.7 13.2": ["teledrama"], "1.3 31.1 4.8": ["distracters"], "7.1 6.4 14.4": ["hudson"], "15.2 2.9 23.3": ["dapple"], "7.3 2.3 13.8": ["sucre"], "12.4 2.3 47.3": ["seviche"], "14.0 10.3 22.6": ["encrustation"], "7.2 15.1 -2.9": ["fraternized"], "2.8 5.6 8.2": ["anabolics"], "8.2 0.0 21.9": ["prego"], "6.5 32.8 12.5": ["finitude"], "-5.7 14.9 10.7": ["coccidioidomycosis"], "-0.1 2.6 12.5": ["famille"], "-2.1 21.2 2.3": ["responsibilties"], "9.4 21.2 11.8": ["recursively"], "6.0 2.9 10.2": ["exalead"], "-2.6 19.6 0.6": ["shariat"], "15.3 5.9 17.7": ["nobs"], "6.3 17.2 18.5": ["waitperson"], "20.2 9.5 9.6": ["climed"], "2.0 8.4 25.0": ["limed"], "7.3 -9.3 26.2": ["olio"], "9.0 8.2 6.2": ["boulevardier"], "5.7 9.8 10.1": ["ingoing"], "4.3 15.9 3.4": ["disjointedness"], "1.4 2.5 14.5": ["columbaria"], "0.2 5.7 10.9": ["ethylmercury"], "-1.2 7.7 7.3": ["faropenem"], "10.5 1.1 14.6": ["unpurchased"], "-1.1 4.9 -5.3": ["courtsey"], "3.5 -5.1 3.9": ["heures"], "7.6 14.1 7.1": ["turbopump"], "12.4 9.4 32.4": ["choucroute"], "1.6 7.2 -0.1": ["weblogging"], "-0.3 13.8 11.7": ["unsterilised"], "6.5 7.3 9.9": ["gayborhood"], "-4.1 8.1 2.4": ["kaddish"], "9.5 14.5 6.2": ["futuristically"], "6.5 7.2 13.7": ["jhatkas"], "13.3 14.8 8.8": ["tricker"], "7.9 10.9 20.6": ["thornless"], "8.8 17.7 5.1": ["overstrained"], "3.2 9.1 0.5": ["interms"], "0.9 12.2 7.4": ["partyless"], "8.3 11.0 14.2": ["chico"], "7.9 6.3 6.3": ["bereits"], "-0.9 0.7 -0.8": ["ean"], "9.5 13.1 10.1": ["outskating"], "7.0 -0.4 16.4": ["hostessing"], "14.4 13.6 13.8": ["ocker"], "9.8 -2.9 5.0": ["extolls"], "7.8 17.0 7.0": ["spazzing"], "-3.1 4.6 11.2": ["geet"], "11.4 11.6 17.8": ["upstroke"], "7.9 44.5 17.9": ["glaive"], "19.2 6.6 18.2": ["trong"], "12.7 10.9 23.9": ["slurpee"], "-2.2 1.8 -2.1": ["intracoronary"], "10.5 10.5 6.5": ["sdk"], "7.5 9.1 7.5": ["malfeasances"], "12.4 17.6 15.0": ["sjambok"], "2.7 11.7 12.3": ["famly"], "-0.8 5.2 10.3": ["stepgrandmother"], "5.3 9.9 6.1": ["downlow"], "7.4 12.9 4.2": ["mockeries"], "-2.5 5.2 2.3": ["ontime"], "10.4 0.2 14.2": ["funfest"], "-0.1 10.7 23.1": ["photoperiodism"], "-8.0 -1.6 6.1": ["assizes"], "-2.5 7.0 5.3": ["semistates"], "-2.7 8.6 5.1": ["coxibs"], "6.2 10.5 17.8": ["festivalgoer"], "1.8 30.0 8.5": ["mischiefs"], "3.2 5.2 0.4": ["alstria"], "4.6 21.0 8.7": ["pommels"], "9.6 4.1 11.7": ["wordperfect"], "1.8 13.4 10.8": ["carbides"], "1.0 7.0 2.3": ["picoliters"], "10.0 18.5 19.3": ["whiteys"], "4.4 26.5 12.7": ["immiseration"], "6.6 15.1 12.5": ["panspermia"], "11.4 -2.2 17.4": ["fiberfill"], "2.1 1.7 13.3": ["viticulturists"], "14.2 10.8 15.6": ["sniffly"], "9.9 22.0 7.9": ["micromanagers"], "3.1 2.2 7.5": ["prosecuter"], "8.8 7.3 16.5": ["cote"], "5.7 13.8 7.3": ["decolonize"], "6.9 5.4 13.7": ["guestworkers"], "5.6 8.0 6.8": ["intermeeting"], "11.4 10.8 15.9": ["spacefarers"], "4.9 12.5 13.4": ["protraction"], "-0.1 7.7 8.3": ["acidizing"], "7.3 10.8 3.2": ["otiose"], "7.1 22.7 18.7": ["irruption"], "12.4 1.2 5.8": ["planogram"], "-2.7 14.8 1.8": ["trotro"], "-2.2 7.7 10.6": ["seroprevalence"], "-2.2 12.6 18.8": ["outdoorswoman"], "14.1 5.5 26.8": ["damson"], "8.2 11.6 6.0": ["switcheroos"], "8.2 17.7 8.4": ["pillages"], "-1.9 -6.7 9.8": ["cochairwoman"], "-4.8 25.2 11.9": ["exclusivism"], "7.2 10.4 2.8": ["trainmen"], "-10.2 9.3 -1.6": ["backdraw"], "6.8 11.4 17.5": ["videocard"], "6.9 10.6 8.0": ["misfold"], "4.7 9.6 19.2": ["salters"], "3.4 2.3 0.3": ["oversells"], "2.4 -7.5 -5.6": ["cofounding"], "16.4 12.2 16.4": ["tangoing"], "2.6 7.1 2.8": ["opend"], "15.6 10.9 11.3": ["conwoman"], "3.7 5.5 1.2": ["tennants"], "9.8 11.4 7.6": ["multimeters"], "4.4 15.3 8.3": ["unitive"], "3.9 17.1 1.4": ["demonises"], "5.6 7.6 12.7": ["dirtbikes"], "12.8 17.4 15.5": ["doozey"], "11.8 7.8 14.3": ["trackies"], "2.0 28.9 12.7": ["procs"], "2.9 7.4 8.2": ["handballers"], "18.8 10.1 7.0": ["renationalised"], "17.0 8.3 15.4": ["suctions"], "9.8 14.2 15.2": ["codpieces"], "-8.3 10.7 7.3": ["ganciclovir"], "8.7 0.4 17.6": ["cheung"], "-1.4 4.0 1.5": ["mahila"], "-3.3 2.2 1.6": ["desmopressin"], "-0.9 4.7 2.4": ["exoneree"], "10.7 4.2 30.3": ["pannacotta"], "-0.1 14.3 3.8": ["encouragers"], "6.4 21.0 9.9": ["fuzzily"], "7.2 2.5 14.9": ["brittany"], "13.6 -0.3 7.1": ["velodromes"], "4.9 12.5 11.7": ["hikikomori"], "5.6 4.3 11.8": ["sedates"], "9.5 1.9 16.8": ["encaustics"], "1.9 12.3 6.5": ["cautery"], "0.5 14.0 5.9": ["macroburst"], "-0.9 5.2 0.5": ["rectifications"], "8.7 35.7 6.5": ["unilateralists"], "7.6 8.7 38.0": ["cracklins"], "12.3 11.4 9.9": ["reorients"], "7.1 -3.7 10.8": ["yw"], "-2.7 16.1 7.3": ["acculturate"], "7.0 15.8 8.4": ["underclasses"], "11.8 6.7 7.9": ["usherette"], "9.2 10.5 11.1": ["scantly"], "1.7 19.7 11.5": ["venial"], "1.0 11.0 5.7": ["pesewa"], "-4.5 10.5 1.0": ["foresightedness"], "19.8 14.7 4.9": ["pyros"], "5.0 12.5 11.4": ["ikramerica"], "17.0 5.3 18.6": ["lawncare"], "10.2 3.6 5.5": ["carillons"], "15.0 11.1 18.2": ["ivies"], "1.5 3.0 18.0": ["muriate"], "12.5 5.2 12.6": ["klatch"], "2.4 -1.7 14.5": ["alf"], "5.0 8.9 7.5": ["nanoproducts"], "6.9 14.4 12.8": ["wraparounds"], "18.8 4.9 2.6": ["foodchain"], "8.3 10.8 14.4": ["mellifluously"], "11.1 8.8 22.8": ["foliate"], "1.7 16.8 3.3": ["cytostatic"], "7.5 15.3 16.8": ["magisterially"], "4.8 12.7 7.3": ["parochially"], "19.5 17.2 17.4": ["uncoils"], "7.8 2.5 11.1": ["domainer"], "9.4 23.5 1.8": ["apocalyptical"], "7.2 7.1 26.3": ["rosehips"], "-1.7 -0.3 8.3": ["bandings"], "9.6 11.3 13.0": ["risker"], "1.9 1.0 20.7": ["ristorante"], "11.0 13.1 13.2": ["cosplaying"], "2.6 2.8 6.6": ["tensioners"], "-8.9 16.9 12.1": ["carnally"], "15.2 18.0 9.6": ["brutalism"], "12.0 7.0 19.2": ["boardies"], "7.6 14.1 15.8": ["aerofoil"], "12.6 5.7 8.6": ["peristaltic"], "14.7 4.0 5.6": ["beginnning"], "19.0 6.3 27.8": ["caca"], "1.8 21.2 7.1": ["intuits"], "10.1 17.5 9.7": ["motherf"], "8.7 14.3 -0.4": ["knottier"], "13.3 7.7 33.4": ["echinoderms"], "-2.0 12.7 3.8": ["sickling"], "-1.5 -0.0 8.0": ["trabecular"], "3.8 6.3 25.6": ["bianco"], "10.7 -2.4 5.9": ["superpremium"], "6.5 28.7 8.9": ["demilitarising"], "9.8 5.7 12.4": ["guqin"], "1.6 1.6 15.5": ["sharemilker"], "-8.4 16.4 7.1": ["baad"], "5.7 4.4 13.1": ["kajal"], "5.7 10.1 11.6": ["nash"], "19.0 1.8 -1.3": ["gmbh"], "-1.9 17.9 6.3": ["fortiori"], "2.8 10.1 23.0": ["hashers"], "0.2 4.2 -3.9": ["vosaroxin"], "2.6 0.7 4.8": ["newsracks"], "5.7 5.7 8.0": ["hairshirt"], "7.1 3.5 7.7": ["countrypolitan"], "4.7 7.5 20.9": ["woodsmoke"], "-4.0 7.1 7.0": ["ypm"], "2.7 5.1 12.0": ["overclockable"], "-2.1 -6.8 -1.8": ["organsied"], "3.6 24.1 11.6": ["speciesism"], "4.6 6.9 9.7": ["mellowest"], "12.1 3.0 11.0": ["towbar"], "16.2 0.3 3.2": ["controverisal"], "12.5 24.3 6.1": ["asshats"], "2.9 4.4 9.4": ["softballer"], "1.0 2.8 6.1": ["overperformance"], "2.2 19.2 4.0": ["losable"], "10.4 5.7 19.8": ["fiftysomethings"], "0.8 6.0 5.7": ["protocal"], "-2.2 10.0 10.0": ["rockish"], "7.9 8.8 3.9": ["summersaults"], "23.6 5.3 8.7": ["lightpole"], "4.3 6.3 10.5": ["hammertoes"], "4.0 11.7 12.6": ["sublevel"], "11.3 10.6 36.5": ["pepitas"], "14.1 19.1 15.6": ["knobkerries"], "8.5 16.2 4.7": ["feminazis"], "-3.6 18.6 5.6": ["misquotation"], "13.8 -1.7 31.4": ["mostaccioli"], "-0.6 -0.3 6.1": ["multiannual"], "8.2 8.1 11.2": ["economywide"], "-0.9 3.3 6.1": ["microcatheter"], "5.2 3.9 11.1": ["travelcard"], "-3.9 16.2 3.6": ["refactor"], "14.9 13.5 14.6": ["burnoff"], "9.0 26.0 6.0": ["smites"], "12.4 14.5 -0.0": ["yacking"], "6.4 10.4 5.6": ["innumeracy"], "7.3 1.6 13.4": ["paleobiologist"], "13.3 2.2 16.9": ["canegrowers"], "6.1 4.9 11.1": ["olympians"], "0.5 -0.4 9.2": ["fuq"], "8.5 25.7 11.7": ["musketry"], "7.3 2.0 9.3": ["brightfield"], "-0.6 11.6 8.9": ["multiplicative"], "10.5 4.9 10.0": ["nanophotonic"], "11.3 12.6 12.9": ["baas"], "8.8 3.0 20.2": ["gabions"], "19.9 13.6 9.8": ["gazillionaires"], "-5.5 3.3 7.7": ["mesothermal"], "9.8 13.1 19.6": ["lipoma"], "1.5 13.0 11.9": ["floridly"], "0.1 6.4 1.8": ["nasyid"], "5.5 15.8 15.5": ["shelterbelt"], "-6.5 19.8 2.8": ["detainments"], "24.3 17.5 25.2": ["lickers"], "5.5 22.8 8.9": ["misruled"], "4.3 10.4 11.5": ["shouldve"], "-4.7 -2.1 8.7": ["flugel"], "9.8 3.1 16.1": ["blondish"], "-1.2 5.2 11.1": ["gpl"], "7.0 24.4 5.0": ["bushido"], "1.0 10.6 7.9": ["janata"], "-6.6 8.7 1.4": ["pathophysiologic"], "2.8 12.3 31.1": ["fattiness"], "11.6 4.5 29.7": ["eggwhites"], "0.7 6.2 37.5": ["vibrio"], "14.8 2.2 27.3": ["blondies"], "10.7 28.2 10.0": ["flagellate"], "18.0 16.6 6.6": ["eurocrats"], "8.9 29.2 18.7": ["nerfed"], "13.9 5.9 8.2": ["molls"], "-0.4 15.8 0.6": ["lionization"], "-0.6 10.1 12.4": ["multiscale"], "0.5 -9.1 0.7": ["toradol"], "-4.9 3.5 -0.4": ["synthetase"], "0.4 0.8 6.4": ["reregistration"], "-5.9 10.5 4.2": ["dominations"], "3.4 2.8 31.9": ["kalo"], "5.0 30.7 22.5": ["worgen"], "4.6 -0.3 18.7": ["fong"], "9.7 5.2 4.0": ["serverless"], "9.1 10.2 0.3": ["unresearched"], "10.9 5.2 -4.9": ["invertors"], "1.6 -1.1 12.5": ["gigabases"], "18.3 12.0 14.0": ["cardie"], "5.7 5.8 0.2": ["stators"], "25.1 5.8 14.1": ["menageries"], "5.2 14.7 15.5": ["attemp"], "2.0 11.6 10.9": ["kahan"], "2.6 8.7 16.1": ["jefferson"], "13.6 3.3 11.0": ["admist"], "14.7 25.8 9.2": ["unbreachable"], "0.4 6.5 26.3": ["suman"], "16.4 3.1 15.0": ["skinsuit"], "13.5 0.3 14.8": ["mantilla"], "4.5 -2.0 3.7": ["ainsi"], "-1.8 11.3 6.5": ["ambulate"], "12.3 21.7 2.3": ["differentness"], "4.7 8.6 22.1": ["drysuit"], "24.1 0.9 35.2": ["tuile"], "13.7 -12.9 -7.2": ["etamp"], "10.3 13.0 17.7": ["tyson"], "13.7 13.2 10.9": ["espy"], "9.3 12.1 11.8": ["underlit"], "-0.3 24.4 5.7": ["lewisite"], "11.9 21.4 5.0": ["monstering"], "25.9 22.2 25.1": ["bandicoot"], "9.1 2.1 3.7": ["nanopatterning"], "19.7 26.8 13.0": ["conquerers"], "18.3 28.0 10.7": ["cannonade"], "4.9 8.6 16.9": ["fossicking", "jip"], "17.2 -0.8 7.7": ["copro"], "3.6 6.7 3.6": ["transduced"], "1.8 -1.4 8.2": ["optimisim"], "6.1 11.0 8.3": ["deflower"], "13.7 14.9 12.9": ["deadman"], "-2.2 21.0 14.3": ["spitefulness"], "4.7 31.0 -1.0": ["downings"], "3.4 9.0 3.5": ["pressrooms"], "13.0 -1.1 9.1": ["rollaway"], "9.0 6.6 22.4": ["whopped"], "14.4 5.1 24.2": ["dills"], "-0.6 12.1 -2.9": ["recapitulating"], "0.5 -5.6 15.5": ["bartends"], "2.1 12.5 7.8": ["diffusive"], "9.6 8.0 5.4": ["roms"], "14.4 3.3 15.3": ["gunked"], "-12.2 6.3 2.4": ["etiological"], "0.0 10.0 8.6": ["trimer"], "7.8 20.4 9.6": ["doomsdayers"], "9.6 14.3 16.1": ["golddigger"], "0.2 10.9 11.4": ["microbiologic"], "11.9 5.0 10.9": ["tamps"], "10.9 15.8 14.7": ["serac"], "-0.9 -3.9 11.6": ["karyotyping"], "6.2 15.2 26.8": ["lantanas"], "21.7 4.1 28.2": ["liquidised"], "18.9 4.6 26.4": ["statice"], "14.4 18.4 12.1": ["alsatian"], "18.7 17.1 18.9": ["eddying"], "-12.3 3.9 5.8": ["relooked"], "2.4 5.1 7.0": ["polyhalite"], "0.3 8.4 4.9": ["concentricity"], "17.5 12.9 36.4": ["junebug"], "8.3 13.2 10.4": ["awesomer"], "6.4 14.5 7.0": ["ccmachine"], "-4.3 4.2 1.6": ["paraplanners"], "7.1 9.0 19.2": ["decollete"], "3.5 17.7 11.7": ["unfortunatley"], "0.5 -6.3 4.1": ["dioxane"], "-3.8 8.0 13.8": ["escheat"], "3.3 6.2 14.3": ["ravi"], "-0.2 5.8 8.2": ["emmy"], "-2.1 11.6 10.3": ["fluorophore"], "2.4 6.2 2.7": ["mixable"], "-2.1 -3.6 4.4": ["ois"], "0.5 -3.7 6.0": ["psa"], "17.9 5.0 20.9": ["glasslike"], "2.3 8.3 9.5": ["equilibrate"], "2.7 3.7 11.5": ["khandsari"], "15.5 9.7 10.9": ["thieved"], "13.6 17.7 13.1": ["babudom"], "21.5 4.6 27.1": ["footless"], "19.7 15.0 22.2": ["amoebic"], "11.8 20.0 11.6": ["greatcoat"], "8.1 10.9 29.9": ["catbirds"], "12.7 8.7 5.7": ["ilegal"], "4.2 -0.0 4.2": ["fortheir"], "10.3 14.3 8.7": ["chromosphere"], "3.8 15.9 0.0": ["pople"], "7.3 5.5 4.1": ["printshop"], "-5.1 15.6 5.6": ["systemize"], "9.9 2.9 13.0": ["digestives"], "12.8 7.7 18.1": ["osteoclast"], "4.5 7.8 17.7": ["darren"], "17.0 11.3 21.0": ["dovecote"], "11.3 6.1 13.9": ["swashes"], "-12.1 8.1 -0.1": ["guidence"], "9.6 -2.4 11.8": ["wye"], "7.2 18.3 3.3": ["superiorly"], "7.0 20.7 15.0": ["rapidfire"], "9.2 11.9 34.6": ["camas"], "0.7 4.2 9.6": ["reguarly"], "5.6 -0.4 8.1": ["strummy"], "5.9 15.5 1.9": ["secondround"], "4.4 4.1 2.8": ["fourt"], "5.1 14.8 10.2": ["bureacrats"], "5.2 19.5 15.2": ["foreshortening"], "10.0 9.7 9.7": ["narked"], "-1.9 4.2 8.1": ["oligomer"], "14.1 14.6 6.1": ["alltogether"], "11.5 11.0 25.1": ["nonna"], "6.5 6.8 8.1": ["ables"], "-6.8 2.0 6.4": ["aks"], "1.2 1.9 14.4": ["granges"], "4.2 17.6 14.4": ["orthorexia"], "5.0 6.0 11.4": ["collets"], "13.9 18.9 1.4": ["dowse"], "11.4 9.3 13.6": ["tremolos"], "7.4 24.6 8.2": ["similitude"], "9.1 3.1 14.3": ["hippyish"], "6.3 22.0 7.4": ["abjection"], "3.3 15.1 12.1": ["circumlocutions"], "4.2 4.1 9.9": ["depigmentation"], "-0.6 8.5 9.0": ["hypersomnia"], "6.8 0.7 11.3": ["neurites"], "-0.6 -0.0 5.2": ["phosphatidylcholine"], "22.3 5.8 12.0": ["gawdy"], "3.7 12.7 10.5": ["emacs"], "1.4 3.3 11.0": ["millibar"], "0.4 6.5 9.9": ["alaskite"], "8.9 17.6 14.2": ["andit"], "9.3 -3.0 -0.4": ["sponsers"], "11.5 15.5 9.8": ["expropriates"], "-0.5 8.1 -0.1": ["fufill"], "7.5 14.5 6.5": ["matchpoints"], "8.9 9.2 3.4": ["thatwill"], "-1.1 11.9 16.5": ["floatplanes"], "13.1 8.6 6.4": ["footlockers"], "1.5 3.6 4.4": ["peginesatide"], "14.9 7.7 13.3": ["puter"], "1.1 6.8 16.2": ["musth"], "0.5 1.2 8.6": ["wouldhave"], "6.6 7.6 14.1": ["harmonizer"], "0.3 9.0 10.1": ["angulation"], "14.9 8.6 28.2": ["cichlid"], "-0.3 21.5 10.4": ["draftnik"], "-5.3 4.3 14.4": ["maganda"], "19.8 5.5 16.8": ["chickenfeed"], "14.3 5.2 17.0": ["anglaise"], "-2.4 9.5 5.9": ["hearin"], "5.6 7.6 27.3": ["shellers"], "18.5 8.3 15.2": ["dodgiest"], "11.2 9.6 3.4": ["thatis"], "8.2 -0.5 9.2": ["biosystems"], "18.0 7.7 15.7": ["volcanically"], "13.8 2.8 1.9": ["switchman"], "6.7 10.6 11.7": ["csv"], "6.7 24.9 -1.2": ["singleminded"], "6.0 9.2 12.2": ["samantha"], "12.6 15.7 3.9": ["useing"], "0.9 9.3 11.2": ["superconduct"], "1.4 1.9 -0.6": ["streamable"], "0.5 24.8 5.6": ["immoralities"], "7.9 1.9 5.8": ["photogallery"], "13.7 2.9 16.0": ["lithographed"], "16.1 6.0 7.3": ["soothers"], "-6.5 14.3 9.9": ["unrounded"], "10.3 16.2 4.0": ["antiproton"], "8.0 10.1 28.7": ["burlapped"], "9.3 10.8 11.4": ["rifting"], "27.4 13.4 14.9": ["handless"], "1.0 4.8 3.1": ["screenname"], "13.8 8.4 12.2": ["redrock"], "4.0 4.5 17.8": ["nitrogenous"], "12.9 12.2 7.2": ["wildcatting"], "9.1 0.7 13.8": ["fixedline"], "9.8 1.6 -3.4": ["betapharm"], "16.4 1.2 16.3": ["kitch"], "9.4 5.5 4.0": ["flipchart"], "17.3 15.2 14.6": ["chesterfield"], "18.9 10.3 12.2": ["breadlines"], "11.1 5.2 9.9": ["asus"], "5.3 14.0 8.7": ["sportsbike"], "6.0 3.0 3.2": ["bioprocesses"], "6.0 7.5 12.1": ["filmer"], "8.2 9.6 3.5": ["bistable"], "11.6 2.1 19.9": ["nubuck"], "-1.1 5.1 3.5": ["vikas"], "7.5 14.2 19.1": ["surfboat"], "9.0 12.8 12.4": ["conjugations"], "-2.5 22.5 8.4": ["badal"], "5.6 24.3 13.1": ["bodybags"], "1.1 15.5 1.7": ["unattained"], "10.2 5.9 9.0": ["diverticulum"], "2.1 16.6 19.8": ["bluing"], "10.8 17.7 15.1": ["petards"], "9.8 15.6 12.7": ["grouchiness"], "2.6 13.9 12.3": ["guilelessness"], "-7.4 4.1 -0.3": ["amendatory"], "5.8 12.4 11.6": ["hornswoggled"], "0.6 25.7 0.7": ["militarising"], "6.2 0.3 9.5": ["mianserin"], "10.9 5.6 22.9": ["heartstring"], "2.1 23.4 10.8": ["underthrowing"], "3.4 7.0 25.8": ["iodized"], "0.2 -4.6 1.2": ["ooba"], "-1.7 15.8 23.6": ["overbet"], "6.1 12.5 7.5": ["picogram"], "7.5 13.6 25.1": ["fossilize"], "19.7 3.0 17.8": ["pice"], "8.0 25.5 6.7": ["spywares"], "0.3 0.8 -0.9": ["excelent"], "3.1 23.8 11.1": ["dialectically"], "2.7 8.6 11.0": ["supernumeraries"], "20.2 4.5 14.6": ["mohican"], "2.7 7.7 15.5": ["nongambling"], "8.5 35.7 20.7": ["dragoons"], "16.8 9.6 16.4": ["diminuitive"], "-2.8 10.0 -4.1": ["nondischargeable"], "5.3 4.4 11.5": ["mutuels"], "0.3 10.2 11.3": ["dists"], "13.4 22.1 12.7": ["dialpad"], "13.7 19.1 16.5": ["cannae"], "10.2 3.4 5.4": ["explorationists"], "-9.3 8.0 8.9": ["misapprehended"], "6.8 23.5 13.4": ["shotter"], "8.8 5.4 13.2": ["covalently"], "-5.9 18.6 3.5": ["passphrases"], "-1.0 9.5 7.9": ["misclassifications"], "19.9 1.8 2.4": ["simliar"], "10.1 14.5 20.9": ["geomancy"], "9.7 23.4 17.7": ["machida"], "1.8 13.6 10.0": ["ringsiders"], "11.0 16.5 6.6": ["satcasters"], "2.8 25.6 5.9": ["machiavellian"], "-2.5 21.4 4.4": ["subcamp"], "8.1 5.9 2.9": ["isssue"], "7.7 23.2 5.1": ["emasculates"], "18.1 7.5 17.3": ["tabernacles"], "11.9 20.3 20.4": ["gulleys"], "8.8 7.6 2.9": ["bookless"], "5.6 5.9 3.0": ["interplays"], "2.2 12.7 7.0": ["interdisciplinarity"], "16.9 -4.2 -9.1": ["aleading"], "16.1 13.6 20.2": ["peta"], "-4.3 5.1 -3.7": ["reconveyance"], "-3.0 12.2 8.1": ["aaye"], "13.1 7.9 21.3": ["suntanning"], "20.0 31.3 10.5": ["interdimensional"], "7.4 16.3 9.9": ["defrosters"], "7.0 9.6 3.1": ["oppositors"], "4.0 23.2 -1.7": ["skillfulness"], "1.1 11.2 7.5": ["beckham"], "5.7 18.9 10.9": ["degaussing"], "4.9 11.2 3.1": ["communty"], "14.3 3.1 -0.8": ["weeek"], "-10.9 6.1 0.0": ["fistulae"], "11.2 6.4 6.4": ["datalogger"], "0.8 -0.2 -1.9": ["desvenlafaxine"], "23.4 9.7 16.0": ["firebird"], "14.0 17.6 25.4": ["companionway"], "13.3 10.3 1.7": ["eyeshades"], "-4.9 3.7 5.6": ["kasina"], "4.4 11.4 8.8": ["asbos"], "-2.3 11.3 6.4": ["opacities"], "6.1 8.9 12.5": ["nanodiamond"], "-0.2 4.7 12.4": ["andesites"], "5.6 4.4 10.3": ["outh"], "-5.1 11.6 7.9": ["oversampled"], "8.2 5.0 0.1": ["thge"], "13.2 9.3 15.0": ["moseys"], "3.8 23.0 15.9": ["unctuously"], "0.7 3.6 8.1": ["chairside"], "16.8 20.7 18.2": ["bloviator"], "0.6 4.2 6.8": ["speedplant"], "12.5 19.6 11.5": ["duffing"], "8.6 6.1 2.3": ["subtenants"], "1.2 0.4 17.5": ["lowe"], "8.6 9.1 15.9": ["cutesiness"], "11.6 7.4 16.4": ["helideck"], "13.9 9.8 30.6": ["tablespoonful"], "15.9 14.3 13.5": ["flunkeys"], "6.6 26.2 9.4": ["egoists"], "-3.1 3.6 7.9": ["chlorthalidone"], "7.7 10.9 2.6": ["adapated"], "10.4 21.0 19.5": ["tolerantly"], "7.7 6.2 9.3": ["superheavyweight"], "8.9 15.1 13.2": ["ragers"], "5.0 -0.7 14.5": ["watchbands"], "3.6 9.5 13.1": ["hdmi"], "7.8 11.8 10.9": ["sphincters"], "5.2 13.1 5.2": ["standalones"], "22.5 0.7 2.4": ["superslim"], "-0.7 13.6 -1.4": ["exculpation"], "11.4 9.0 8.5": ["wildy"], "15.3 13.9 28.1": ["defrosts"], "1.6 13.0 15.1": ["aisa"], "24.0 2.4 10.8": ["zillionaires"], "-3.7 14.3 7.9": ["enumerations"], "9.1 19.9 18.3": ["puckheads"], "11.9 9.8 7.8": ["sadomasochist"], "2.9 3.6 16.4": ["kul"], "1.1 5.8 16.7": ["kanila"], "8.8 6.5 1.8": ["bioimaging"], "10.8 25.6 20.1": ["boatswain"], "16.9 12.0 9.1": ["magnificant"], "13.4 9.7 18.9": ["bain"], "12.2 -0.2 4.3": ["insertable"], "21.0 12.2 16.4": ["pimpled"], "4.6 9.2 -7.1": ["unexcelled"], "6.0 8.6 5.9": ["naturalise"], "8.8 9.3 15.4": ["unvaried"], "5.7 9.2 9.0": ["pericytes"], "3.8 5.2 7.2": ["tje"], "9.6 15.8 25.8": ["overbake"], "8.0 4.7 9.8": ["oncourt"], "6.1 5.3 5.9": ["manque"], "0.8 15.5 4.7": ["doveish"], "-3.4 5.5 -4.5": ["learing"], "7.2 10.3 32.8": ["soursop"], "30.3 10.9 29.5": ["brachiosaurus"], "5.7 0.1 8.8": ["cubase"], "-0.5 14.1 7.7": ["proprioceptive"], "5.8 1.5 9.4": ["andrea"], "7.9 5.6 12.3": ["tutted"], "14.2 5.1 17.2": ["wainscot"], "2.4 9.5 4.2": ["visi"], "16.6 15.2 14.6": ["fookin"], "0.1 14.9 10.2": ["predetermines"], "-3.4 -1.4 9.5": ["fenretinide"], "9.6 7.2 22.0": ["vicuna"], "-8.2 2.8 5.2": ["prosthodontics"], "4.3 10.4 23.8": ["towhees"], "12.1 8.9 27.8": ["toucher"], "0.0 8.1 6.0": ["tessitura"], "5.7 0.9 13.8": ["sculled"], "-2.6 6.4 7.5": ["tention"], "7.5 15.8 14.4": ["bradley"], "1.2 0.3 10.4": ["governesses"], "-2.7 7.0 2.6": ["durring"], "8.7 23.4 8.5": ["neccessity"], "5.9 12.0 23.5": ["crazing"], "7.8 4.8 24.0": ["pinelands"], "-11.5 6.6 2.1": ["advisee"], "-1.6 13.6 8.6": ["hybridoma"], "-0.9 -5.2 -4.2": ["lectureships"], "0.2 13.1 6.8": ["homosexualist"], "0.5 24.4 3.6": ["deludes"], "8.8 19.6 12.6": ["unseemliness"], "7.3 17.1 9.6": ["exasperatedly"], "20.1 4.0 15.2": ["pompadoured"], "8.5 6.9 1.7": ["torchings"], "18.5 16.3 9.4": ["authories"], "-3.7 5.4 4.3": ["streptokinase"], "12.0 23.4 6.2": ["lunkheads"], "5.5 4.1 18.6": ["musicmaking"], "17.6 5.4 11.5": ["spokesdog"], "6.2 9.2 1.7": ["sowie"], "3.6 -3.2 21.0": ["nonholiday"], "1.3 1.5 28.1": ["ika"], "6.8 1.7 22.0": ["teng"], "7.9 10.2 8.9": ["raucus"], "1.8 13.7 20.9": ["sclerotinia"], "14.1 10.2 14.1": ["pedalers"], "12.1 13.0 17.7": ["lycanthropy"], "12.8 -4.4 3.0": ["miffs"], "-1.7 -5.2 3.4": ["hydrotreating"], "10.6 3.4 44.8": ["creels"], "17.1 35.9 19.5": ["stargate"], "10.2 6.7 20.8": ["riviera"], "-4.1 18.8 10.3": ["abjured"], "15.2 -6.1 0.9": ["saidit"], "7.5 7.8 -0.9": ["sinc"], "5.3 8.7 7.2": ["entrepreneurships"], "7.0 17.5 -1.0": ["disenchanting"], "13.2 3.6 41.4": ["shroom"], "7.4 14.7 3.1": ["visioned"], "13.8 4.3 15.8": ["kipunji"], "5.0 1.4 5.6": ["megamix"], "6.6 11.6 10.1": ["nebraska"], "3.4 20.7 4.4": ["nonalignment"], "6.9 27.8 8.1": ["manipulatively"], "24.6 3.8 7.2": ["squillion"], "10.8 3.6 8.2": ["interes"], "1.9 6.2 14.7": ["maxilla"], "-6.2 -3.2 3.6": ["toastmasters"], "9.4 11.5 3.2": ["tickin"], "2.4 23.9 0.9": ["unexcusable"], "12.2 -0.7 16.3": ["lange"], "-3.2 7.5 7.0": ["bailment"], "3.1 13.6 12.5": ["repellency"], "3.0 2.6 12.8": ["eso"], "16.1 12.4 29.6": ["bakso"], "1.7 4.6 12.5": ["christine"], "12.2 18.7 11.5": ["untidily"], "7.5 13.7 8.7": ["uninhibitedly"], "13.5 5.8 31.0": ["flans"], "8.6 12.8 7.6": ["memorialise"], "-6.9 0.1 3.5": ["cpo"], "2.8 -2.2 3.1": ["conservatorium"], "10.4 7.1 4.7": ["micelle"], "11.7 12.8 14.3": ["transshipping"], "14.5 4.0 35.6": ["pastitsio"], "4.9 8.2 3.7": ["bekannt"], "16.1 3.1 6.3": ["touche"], "21.4 11.7 8.2": ["catnapping"], "5.2 5.5 10.0": ["annas"], "16.3 15.7 23.1": ["disembowelling"], "3.1 5.8 4.2": ["tanpura"], "7.9 9.3 10.6": ["geat"], "6.2 6.7 14.5": ["reamers"], "5.1 2.5 8.5": ["soild"], "7.2 2.6 17.5": ["stonemasonry"], "-1.9 -1.4 9.9": ["pmand"], "16.0 4.3 9.0": ["tradie"], "6.7 6.8 17.8": ["waterers"], "9.1 -1.5 20.8": ["tsai"], "16.3 16.0 5.4": ["bamboozles"], "7.7 8.7 6.6": ["mbaqanga"], "-4.6 20.3 6.2": ["nonverbally"], "16.2 11.7 25.0": ["orangish"], "17.0 24.1 19.9": ["grapeshot"], "20.0 18.1 11.7": ["brewin"], "9.9 8.2 19.6": ["stibnite"], "3.9 17.2 7.8": ["speechlessness"], "4.1 0.7 3.6": ["cybercast"], "8.5 14.8 11.7": ["kissin"], "16.9 8.2 35.1": ["limas"], "7.6 3.3 6.6": ["nonelectric"], "1.0 2.5 6.9": ["cingulate"], "13.4 15.2 12.7": ["roc"], "7.9 12.1 8.9": ["bazaaris"], "4.0 10.8 18.4": ["sufganiyot"], "4.4 9.3 7.6": ["outpowered"], "15.2 13.4 11.7": ["ahhhhh"], "2.1 -1.1 8.1": ["elligible"], "1.9 -5.3 -1.1": ["directeur"], "3.8 6.1 17.8": ["gelcoat"], "4.9 -1.4 14.1": ["misdeclared"], "10.8 2.8 16.4": ["uggs"], "-6.0 5.5 1.4": ["codirectors"], "-1.8 4.7 -10.0": ["annonymous"], "2.6 2.4 -1.9": ["representitives"], "7.2 4.2 6.7": ["whenhe"], "14.7 12.8 16.8": ["furring"], "15.5 8.7 11.5": ["backpage"], "-4.3 10.3 4.2": ["hota"], "18.1 8.3 -1.3": ["touchpaper"], "12.9 13.1 5.2": ["revivify"], "5.4 10.8 32.6": ["crotons"], "12.1 -0.3 13.8": ["inplace"], "-0.1 25.5 5.6": ["wmd"], "-1.2 15.1 0.2": ["inveighs"], "12.7 17.1 20.4": ["doggers"], "7.0 24.4 8.8": ["proliferations"], "-2.6 1.3 11.1": ["sevelamer"], "2.6 5.2 -1.0": ["cardiomyopathies"], "16.3 17.4 21.0": ["dwarfish"], "8.7 1.3 9.1": ["daar"], "4.5 -2.6 -1.0": ["accoridng"], "10.2 28.9 -2.7": ["triangulates"], "3.0 10.1 4.3": ["patriation"], "1.9 10.4 7.2": ["cyclooxygenase"], "2.0 1.7 -1.6": ["reproted"], "-0.4 11.6 2.9": ["worklist", "counries"], "-10.9 14.9 1.8": ["rehospitalizations"], "-6.2 5.3 5.6": ["couchsurfing"], "14.2 3.2 17.4": ["pelota"], "-2.1 12.6 -1.7": ["contradictorily"], "16.7 11.8 37.8": ["elkhorn"], "3.5 5.4 13.5": ["microdiamonds"], "15.4 -2.9 17.0": ["fibreboard"], "9.4 18.2 17.8": ["nonchemical"], "-0.6 4.8 15.4": ["resample"], "-2.0 0.4 0.1": ["unani"], "1.8 13.6 2.7": ["wnat"], "2.4 10.1 12.7": ["linework"], "15.3 5.0 6.7": ["iniatives"], "8.1 8.5 1.6": ["concerened"], "1.7 12.1 19.3": ["procreated"], "16.2 4.2 15.9": ["hoedowns"], "11.5 10.3 8.9": ["basemap"], "18.1 5.2 6.8": ["jabbered"], "9.9 16.8 5.9": ["hypercar"], "8.4 5.2 17.0": ["riley"], "20.0 10.6 23.9": ["capybaras"], "-5.1 16.8 6.3": ["plasminogen"], "6.1 14.7 16.7": ["spicules"], "-7.1 12.9 7.1": ["locoregional"], "13.4 8.3 4.6": ["econoboxes"], "16.2 14.1 10.8": ["gridirons"], "8.3 7.4 45.5": ["kombu"], "-0.0 15.5 5.3": ["widemen"], "-9.2 10.1 21.4": ["throwout"], "5.5 10.7 7.4": ["cowpunk"], "5.5 5.3 0.7": ["concieved"], "4.1 -7.6 12.0": ["carwashing"], "-6.5 17.8 -0.2": ["resuscitative"], "-1.4 10.6 1.7": ["pround"], "14.3 12.2 0.7": ["unlink"], "-8.0 9.6 5.7": ["downzoned"], "22.3 11.6 12.5": ["cuddliest"], "2.4 14.3 5.9": ["groundedness"], "11.7 15.4 17.1": ["inexpertly"], "12.6 5.4 14.1": ["pourers"], "-5.1 7.3 18.1": ["houseboating"], "14.9 8.4 17.6": ["weet"], "17.6 16.3 11.2": ["curser"], "5.5 15.5 17.5": ["animes"], "4.6 2.3 1.6": ["tagless"], "-0.8 5.1 8.3": ["stylistics"], "-0.3 30.0 15.6": ["fraggings"], "0.4 13.9 0.3": ["frankest"], "3.1 6.4 24.8": ["malai"], "12.2 4.9 15.6": ["elvis"], "25.1 14.6 16.4": ["crenellated"], "-3.9 15.4 6.9": ["begum"], "2.3 -0.5 4.3": ["halfhour"], "19.3 19.0 17.5": ["snuffle"], "15.5 17.1 23.1": ["huanglongbing"], "-1.8 3.1 1.3": ["comparedto"], "0.2 8.3 8.8": ["kilims"], "7.6 16.2 7.2": ["spliceosome"], "8.2 15.4 22.1": ["sleety"], "1.8 1.3 12.6": ["unrented"], "2.1 3.6 8.0": ["sok"], "-11.9 4.6 5.5": ["prehypertensive"], "9.0 -2.6 11.2": ["questa"], "7.7 4.0 31.5": ["paellas"], "11.4 7.9 1.5": ["worldover"], "0.8 9.1 18.3": ["nisin"], "7.7 4.6 5.0": ["parkings"], "6.6 19.6 6.4": ["husbanded"], "6.5 4.7 5.5": ["suffocations"], "0.9 6.0 2.4": ["homologues"], "2.4 15.7 15.5": ["sanshou"], "3.6 9.2 16.7": ["vocalisation"], "5.3 5.4 6.8": ["theability"], "-2.6 8.4 3.3": ["sewa"], "5.6 -0.2 5.9": ["edo"], "5.0 2.0 4.7": ["twi"], "15.0 4.6 8.5": ["perfluorocarbon"], "1.0 13.5 7.8": ["intermolecular"], "24.0 18.9 24.8": ["schlong"], "12.7 12.3 23.6": ["mosasaurs"], "5.1 3.6 18.6": ["sideburn"], "0.1 8.0 35.8": ["frogging"], "2.4 23.5 19.5": ["privateering"], "4.4 11.1 11.4": ["topliner"], "0.7 -1.8 5.5": ["carnallite"], "-3.1 1.0 1.2": ["hepatologist"], "12.1 11.7 16.2": ["lawned"], "-6.6 4.8 12.0": ["penetrance"], "6.6 11.4 7.8": ["propogate"], "-4.6 12.1 9.1": ["autobiographically"], "-4.3 14.5 2.1": ["adventitious"], "16.0 12.7 25.5": ["cassowaries"], "-0.7 5.4 4.1": ["innoculate"], "10.1 6.9 2.3": ["wating"], "8.5 12.5 10.1": ["bracketologist"], "-2.4 -3.3 6.2": ["chargeoff"], "-4.3 3.5 12.4": ["housebreaks"], "15.0 4.2 16.6": ["swagged"], "10.8 11.3 20.3": ["calvados"], "18.9 3.6 8.3": ["ancilliary"], "12.3 5.0 36.1": ["multispecies"], "17.5 13.9 15.0": ["hiving"], "-0.1 1.4 7.0": ["probabtion"], "0.9 6.6 13.9": ["coumadin"], "19.8 7.7 11.3": ["poofed"], "4.4 7.0 25.6": ["maltiness"], "-5.8 11.3 -2.9": ["encouragment"], "6.5 11.3 18.0": ["macking"], "7.0 17.3 18.3": ["ritualism"], "27.7 18.7 18.6": ["prehensile"], "4.7 2.8 15.4": ["baculovirus"], "10.0 2.4 12.4": ["retarder"], "5.6 2.9 33.3": ["tasso"], "11.6 15.3 9.3": ["pointscoring"], "4.5 5.5 16.7": ["scaping"], "-6.0 -0.5 1.4": ["supportiveness"], "14.6 14.5 5.5": ["pokerfaced"], "9.3 8.9 19.6": ["millrace"], "12.3 11.8 24.7": ["cochineal"], "6.4 10.2 6.2": ["habla"], "-2.3 11.7 6.1": ["wou"], "13.4 21.4 38.8": ["weedline"], "18.4 22.6 15.7": ["phantasms"], "10.9 4.1 15.7": ["buena"], "6.6 -3.7 -1.2": ["vye"], "17.9 19.2 10.7": ["shazam"], "-1.4 0.8 17.7": ["zins"], "4.1 3.3 -1.6": ["paedophilic"], "5.2 10.2 10.0": ["plainchant"], "-0.6 -1.3 -1.7": ["firstyear"], "15.7 20.1 7.7": ["archduke"], "-6.8 7.6 6.0": ["desicion"], "1.0 7.3 4.4": ["continentally"], "2.1 1.1 7.7": ["pregant"], "13.9 15.1 4.5": ["disintermediate"], "18.6 3.7 8.1": ["seatless"], "16.2 8.7 8.1": ["branchless"], "16.5 5.9 9.4": ["nly"], "4.6 13.2 12.7": ["tsigili"], "12.9 11.0 13.6": ["mancession"], "7.4 20.1 8.3": ["mutagen"], "10.1 14.9 2.9": ["prophesised"], "3.8 13.9 19.7": ["esteros"], "16.9 4.5 25.0": ["sultana"], "-4.1 3.1 5.6": ["nancial"], "-4.5 1.2 3.8": ["subgrants"], "22.8 11.7 28.8": ["nubbins"], "3.7 15.5 14.3": ["noy"], "0.9 2.7 3.3": ["glycols"], "17.0 2.2 -1.1": ["unsexiest"], "6.5 -1.4 16.0": ["fei"], "14.7 5.2 19.3": ["puffier"], "0.5 7.6 1.8": ["duma"], "5.3 6.9 13.7": ["draughtsmanship"], "5.2 11.6 0.3": ["roadgoing"], "1.0 3.1 16.0": ["ranchette"], "15.8 17.5 17.4": ["scarper"], "15.8 9.6 9.0": ["maharajahs"], "6.7 19.2 15.3": ["garimpeiros"], "9.5 7.1 2.7": ["thyristor"], "8.5 1.6 0.9": ["derated"], "12.6 7.9 20.7": ["overcut"], "-2.1 5.3 16.5": ["unfermented"], "15.4 6.1 12.0": ["superwealthy"], "7.0 14.8 14.6": ["clinginess"], "13.9 10.3 10.2": ["disbelievingly"], "10.7 13.3 12.4": ["truing"], "-0.9 1.3 9.4": ["sealcoating"], "6.5 -2.5 7.1": ["lengthly"], "4.4 3.9 20.0": ["americano"], "-0.4 8.2 -6.5": ["eversince"], "3.0 8.8 18.7": ["deerstalker"], "3.1 14.6 12.0": ["overtrading"], "4.6 -2.4 10.8": ["cyn"], "7.8 20.9 -4.1": ["sundering"], "14.9 7.2 21.9": ["dustpans"], "9.3 7.8 6.1": ["pillarless"], "-8.0 8.2 5.2": ["apprises"], "18.9 20.6 22.7": ["thunderhead"], "11.9 7.2 2.2": ["quadricycle"], "11.5 16.5 -0.7": ["gauss"], "2.5 6.5 2.2": ["passout"], "9.6 6.2 3.5": ["icloud"], "2.2 6.9 14.2": ["strawweight"], "5.0 6.3 6.1": ["untenably"], "10.5 21.2 5.5": ["perimetre"], "11.3 -6.5 -8.2": ["opthalmology"], "10.4 8.9 3.5": ["sententious"], "-7.0 6.6 8.2": ["purities"], "2.5 -2.2 7.6": ["ica"], "3.7 3.2 -2.6": ["telemedical"], "11.3 10.7 4.1": ["boxee"], "6.4 -2.1 4.8": ["sciatic"], "31.7 7.9 28.9": ["fishtank"], "8.2 15.2 12.0": ["wanta"], "0.4 7.7 16.1": ["nuclease"], "15.4 1.4 19.7": ["bridalwear"], "12.4 10.8 5.8": ["kwiry"], "0.3 16.9 3.9": ["annoint"], "2.5 3.5 5.9": ["teriflunomide"], "3.7 10.5 18.2": ["lifebelts"], "11.3 6.5 14.4": ["veh"], "17.3 7.5 27.9": ["haft"], "14.1 11.2 -4.6": ["nonmoving"], "-3.0 20.8 11.5": ["retcon"], "14.4 7.9 4.8": ["paraphenalia"], "-3.1 7.0 2.7": ["isues"], "-4.6 1.5 7.3": ["esterification"], "8.7 15.8 9.7": ["rends"], "8.8 16.8 15.1": ["crappiness"], "0.0 3.2 9.0": ["emi"], "0.0 15.7 5.0": ["unconservative"], "-2.7 0.7 -0.1": ["ultrasonographic"], "-1.1 19.6 11.0": ["teleology"], "1.3 27.4 11.3": ["lovingkindness"], "4.4 2.4 7.1": ["vier"], "18.1 14.8 10.2": ["gabble"], "1.1 -0.9 10.0": ["hous"], "14.4 23.6 15.5": ["poofter"], "13.9 34.1 3.2": ["facism"], "5.8 12.6 9.0": ["biden"], "9.3 6.4 4.2": ["angop"], "3.2 -0.3 24.1": ["paczkis"], "14.3 3.4 14.3": ["oom"], "18.3 23.9 24.7": ["lummox"], "23.7 25.1 17.6": ["jingo"], "4.9 -0.1 7.7": ["violoncello"], "12.9 11.9 14.6": ["inbreds"], "4.2 18.8 9.2": ["whoredom"], "9.2 -1.8 30.6": ["coppa"], "-2.9 4.7 6.6": ["autosampler"], "9.1 30.0 2.2": ["antipersonnel"], "-0.2 2.9 6.9": ["ambulette"], "7.8 6.3 11.2": ["discharger"], "14.9 17.8 3.7": ["actuates"], "11.1 15.0 25.6": ["taproots"], "-2.6 5.3 8.8": ["otic"], "6.1 14.3 9.2": ["unsanitized"], "17.6 20.2 15.0": ["bullyboy"], "9.9 19.4 5.7": ["extragalactic"], "-2.5 -1.1 12.4": ["nontenured"], "5.4 18.1 15.7": ["katas"], "7.9 1.0 -9.4": ["evangelizes"], "18.5 1.2 19.1": ["decoupaged"], "5.2 13.3 8.7": ["amakhosi"], "1.2 3.6 12.4": ["busbars"], "-0.1 6.3 5.4": ["flyleaf"], "-2.5 10.5 15.6": ["rohe"], "-3.6 3.3 6.0": ["colistin"], "33.7 1.3 7.6": ["companie"], "6.0 1.4 26.0": ["dulce"], "10.9 5.0 0.4": ["biophysicists"], "-4.9 3.0 13.8": ["durometer"], "5.1 11.9 5.0": ["kilometric"], "-10.2 12.9 16.7": ["subaccount"], "11.4 18.8 18.5": ["hogtie"], "8.7 14.0 9.5": ["clubbable"], "12.9 8.5 0.1": ["twitterati"], "-3.3 7.5 10.8": ["lowkey"], "5.8 -2.1 10.6": ["muchas"], "19.7 25.2 13.1": ["peashooter"], "10.7 16.4 6.0": ["staright"], "4.2 8.5 4.2": ["rrusso"], "4.3 15.2 8.9": ["unluckier"], "1.0 19.4 13.5": ["nucleolus"], "7.7 11.3 12.2": ["clavinet"], "6.4 2.3 8.4": ["wss"], "19.7 7.8 32.8": ["oxblood"], "-4.8 8.8 10.9": ["thioredoxin"], "12.5 11.7 11.2": ["dogsbody"], "-5.5 4.7 5.8": ["readmittance"], "19.0 0.9 26.3": ["geta"], "4.6 11.2 -0.4": ["critcism"], "10.4 5.3 -1.7": ["slipstreamed"], "0.6 5.9 5.8": ["phonology"], "-6.3 7.3 4.9": ["lege"], "9.1 9.9 11.8": ["rambunctiousness"], "-2.3 4.7 2.3": ["homiletics"], "-9.8 3.5 7.3": ["fullfilled"], "4.9 2.4 17.4": ["terno"], "1.3 4.7 1.8": ["datafeeds"], "5.3 -4.1 2.7": ["forprofit"], "-5.6 6.6 15.9": ["crus"], "7.3 6.2 13.7": ["ironmaking"], "-4.5 4.6 -0.6": ["rostrvm"], "-0.5 5.3 6.7": ["someof"], "12.9 3.5 34.1": ["tomatos"], "-3.9 5.0 0.7": ["thta"], "3.7 18.8 7.5": ["pseudogap"], "9.1 0.6 12.7": ["flotel"], "13.3 12.7 5.5": ["outgrossed"], "6.6 0.9 3.2": ["ative"], "10.2 16.8 9.1": ["warmist"], "5.7 27.5 11.9": ["heedlessness"], "-2.6 17.7 8.7": ["facetiousness"], "11.1 12.4 9.0": ["polder"], "9.7 9.2 8.7": ["transgenerational"], "10.1 11.1 9.0": ["chestful"], "5.7 2.2 18.4": ["andare"], "2.0 -1.5 0.9": ["orgainsed"], "3.2 2.9 -6.5": ["phonautograms"], "-6.0 6.3 5.5": ["deceases"], "4.4 3.4 5.1": ["ign"], "-0.0 8.5 4.7": ["betterball", "fusionists"], "-0.3 21.0 22.7": ["karl"], "1.2 13.0 4.9": ["wrester"], "-1.7 6.7 15.9": ["tangata"], "15.9 28.5 10.3": ["abysses"], "6.5 -1.0 1.5": ["tranch"], "9.6 -5.1 3.6": ["reman"], "1.0 7.4 8.7": ["indicies"], "2.0 -0.1 -3.9": ["cabozantinib"], "1.7 19.0 19.7": ["reraising"], "3.9 1.8 13.1": ["shoplots"], "11.1 15.5 6.5": ["verticalization"], "17.2 4.3 2.3": ["yeserday"], "9.4 5.0 12.2": ["poolhouse"], "7.8 19.7 13.7": ["unlikeliness"], "11.3 10.9 11.4": ["nonmagnetic"], "21.0 13.1 17.7": ["protists"], "9.1 2.3 11.7": ["approximatley"], "14.7 13.2 17.4": ["forbes"], "12.4 20.3 3.1": ["hackings"], "4.7 14.6 15.9": ["kopek"], "4.7 13.1 9.8": ["unrattled"], "2.8 -4.7 9.3": ["sunsplashed"], "0.9 1.5 -0.9": ["devolo"], "3.8 4.3 5.8": ["reprices"], "13.1 9.0 12.7": ["wifebeater"], "0.2 10.2 21.3": ["hoppiness"], "-0.8 5.7 10.0": ["qualia"], "-11.2 0.5 4.0": ["premedication"], "1.2 10.5 1.9": ["chemiluminescence"], "-2.0 2.3 5.2": ["recognisance"], "1.7 16.1 3.1": ["loopt"], "6.6 12.4 9.3": ["replan"], "-6.4 15.9 5.5": ["surrenderees"], "6.8 -0.4 25.9": ["tangelo"], "7.0 12.5 13.3": ["flowin"], "12.9 5.0 20.2": ["mooched"], "3.6 -0.1 8.1": ["cee"], "5.3 2.6 -0.8": ["intitiative"], "13.0 7.6 13.3": ["corkers"], "15.9 14.4 9.5": ["switchovers"], "12.5 0.5 16.3": ["reales"], "6.4 15.6 16.6": ["bruv"], "18.1 15.5 32.9": ["puddin"], "-2.0 15.5 6.2": ["chemoresistance"], "1.2 1.9 2.8": ["recarpeted"], "-5.0 6.0 1.8": ["speical"], "3.8 1.8 10.3": ["washability"], "14.5 28.4 8.7": ["unconceivable"], "-1.6 0.2 13.5": ["chester"], "5.0 3.7 3.2": ["thatgamecompany"], "20.3 -0.1 28.2": ["gateaux"], "6.9 9.0 13.7": ["wayyy"], "-1.3 11.0 9.0": ["upsetter"], "4.7 10.7 11.3": ["posteriorly"], "14.4 3.6 29.0": ["crustless"], "-3.8 17.7 5.4": ["partyman"], "-3.1 5.4 11.2": ["rushees"], "-0.2 7.4 8.7": ["mompreneur"], "5.8 10.5 6.9": ["functionalization"], "-6.5 19.7 -0.1": ["postconflict"], "-2.3 13.2 3.3": ["cauterization"], "-0.5 16.0 6.2": ["overanalysis"], "9.4 9.9 20.1": ["pinstripers"], "10.6 11.6 3.3": ["coiner"], "-6.0 9.1 2.5": ["theorises"], "3.2 7.2 7.2": ["pabaon"], "3.0 12.2 23.2": ["unsprayed"], "-2.8 3.9 1.2": ["ipratropium"], "6.0 -8.6 22.4": ["hongbao"], "14.7 11.1 23.7": ["duiker"], "-0.2 13.9 0.5": ["spritual"], "0.7 7.1 5.7": ["tevez"], "-4.8 14.4 3.4": ["priorites"], "3.2 5.5 13.7": ["ventless"], "12.1 19.9 6.2": ["depersonalizing"], "11.1 17.8 17.1": ["hagglers"], "8.7 0.2 19.4": ["drumlines"], "10.6 9.1 22.6": ["subducted"], "3.8 14.1 8.1": ["sackmaster"], "0.2 21.4 6.2": ["degredation"], "3.2 8.7 31.0": ["camote"], "6.9 0.9 27.4": ["huaraches"], "12.9 17.0 18.7": ["respire"], "14.7 7.3 20.3": ["snackable"], "6.0 8.6 9.9": ["rhyolitic"], "7.1 12.1 7.7": ["perving"], "18.5 10.0 12.4": ["shemale"], "19.3 11.4 14.6": ["cubit"], "3.6 5.0 12.5": ["barras"], "7.1 0.5 12.4": ["speci"], "3.5 6.6 17.7": ["clavicles"], "1.3 25.3 8.1": ["idealogues"], "10.6 3.6 10.0": ["norton"], "1.2 5.1 6.7": ["grama"], "6.7 9.5 0.6": ["flatus"], "17.6 1.4 28.7": ["horsing"], "12.8 7.4 8.6": ["handbrakes"], "14.1 14.6 37.1": ["pondweed"], "2.4 4.6 4.0": ["replicability"], "2.5 8.9 22.2": ["clarets"], "4.8 21.9 3.9": ["khans"], "16.8 12.7 21.2": ["addle"], "17.7 -5.7 10.1": ["vgc"], "14.8 8.8 11.2": ["footdragging"], "1.6 10.4 3.3": ["contemporaneity"], "-0.3 3.6 10.4": ["ilo"], "7.3 14.7 25.0": ["breakwalls"], "5.0 -1.1 8.4": ["preparator"], "7.4 -2.4 11.9": ["jer"], "6.5 8.0 12.9": ["torrefaction"], "-2.2 9.4 1.6": ["diyat"], "5.4 12.9 8.5": ["twitchiness"], "18.9 4.6 5.0": ["catwalker"], "-0.2 0.7 17.5": ["camelids"], "-3.6 3.7 2.3": ["vocalised"], "11.3 21.9 10.2": ["solitons"], "0.9 2.5 16.6": ["taggings"], "16.7 8.3 -0.3": ["redenominate"], "1.0 16.3 5.2": ["bhaiyya"], "3.7 7.5 9.6": ["lipidomics"], "-9.1 10.5 10.7": ["onsets"], "5.4 6.8 13.3": ["melo"], "18.2 28.0 6.3": ["spoofer"], "-2.9 2.0 4.8": ["nonemployee"], "4.7 0.7 7.8": ["directx"], "7.0 17.3 3.2": ["kiling"], "0.6 6.5 19.5": ["mian"], "4.4 6.8 14.8": ["kathakali"], "9.8 0.9 9.6": ["trent"], "12.0 14.4 -0.1": ["defenestrated"], "-1.0 -0.9 10.9": ["prosthetists"], "12.4 7.8 36.7": ["molcajete"], "-7.5 6.0 3.1": ["nonperformers"], "19.0 0.1 17.2": ["portaloo"], "13.3 17.6 7.1": ["levellers"], "4.0 -1.4 0.6": ["vd"], "10.7 10.0 6.7": ["monoxide"], "16.5 10.3 12.9": ["garishness"], "13.9 9.5 0.8": ["remoulded"], "9.1 8.6 12.0": ["pylori"], "8.4 21.1 8.4": ["tendancies"], "12.8 15.5 13.1": ["kerbstones"], "1.4 -2.3 6.4": ["mezzos"], "-2.4 11.4 19.1": ["subsamples"], "6.9 6.3 13.5": ["perez"], "12.8 17.9 26.3": ["snorkeller"], "17.7 -1.7 11.7": ["reinflated"], "26.5 20.4 29.9": ["medusa"], "0.5 19.1 5.4": ["parasomnia"], "4.6 5.4 15.7": ["aquaporin"], "8.5 6.5 16.4": ["divertissements"], "1.8 11.3 6.3": ["backdoored"], "9.6 16.8 16.0": ["lovesickness"], "2.6 19.9 15.0": ["kindliness"], "0.6 -2.7 6.1": ["liga"], "1.4 1.8 12.7": ["hydrofracturing"], "4.0 3.9 4.7": ["clergywoman"], "4.4 2.4 13.0": ["strath"], "17.6 20.2 12.2": ["conquistadores"], "-7.1 29.2 7.1": ["maliks"], "8.6 14.2 7.0": ["nonpolar"], "11.3 5.3 7.9": ["spotlessly"], "1.4 5.7 10.9": ["solutes"], "4.3 27.2 19.7": ["seaways"], "9.7 17.1 9.0": ["fibbers"], "15.4 11.5 11.6": ["boardgames"], "6.3 4.2 8.9": ["uncontentious"], "8.3 8.8 6.7": ["cctv"], "-3.3 4.2 4.0": ["trabectedin"], "23.4 1.7 16.1": ["wodge"], "5.9 0.6 9.6": ["wallmounts"], "4.3 1.4 15.0": ["ayi"], "-1.7 23.7 5.5": ["devisive"], "0.5 4.1 9.3": ["preprimary"], "2.7 14.7 14.9": ["rubbin"], "12.1 11.0 19.9": ["schuss"], "-2.1 16.1 6.7": ["disrepect"], "4.7 14.9 7.4": ["embarassingly"], "-0.7 23.0 2.3": ["azaadi"], "9.3 1.6 5.1": ["caroline"], "-8.1 8.4 4.1": ["correlational"], "16.9 10.7 6.2": ["futurologists"], "-0.3 14.7 9.8": ["frustation"], "0.0 18.8 10.4": ["shonen"], "9.1 9.5 -4.1": ["locr"], "3.7 13.4 12.7": ["zara"], "-8.2 -0.8 5.2": ["transfemoral"], "10.9 7.3 6.3": ["toshiba"], "-8.9 2.9 -1.1": ["bacteraemia"], "0.2 5.5 4.5": ["multiviewer"], "-8.1 5.8 20.3": ["earliness"], "-0.7 15.9 9.6": ["tey"], "20.0 14.5 8.4": ["trillionaire"], "2.9 15.1 13.6": ["fussin"], "3.2 15.3 9.0": ["monovision"], "4.4 16.3 7.8": ["outexecuted"], "5.1 11.0 -0.5": ["panegyric"], "5.1 5.1 17.0": ["saturdays"], "7.3 11.2 12.5": ["likeably"], "5.1 1.0 5.5": ["dignatories"], "0.7 0.7 44.1": ["bacalao"], "5.1 14.2 14.8": ["heatworld"], "5.4 0.9 6.0": ["dynos"], "-3.6 0.9 3.3": ["videojournalist"], "10.0 15.5 13.4": ["bivouacs"], "3.3 6.4 0.6": ["organometallic"], "0.9 16.2 15.6": ["preventives"], "-1.1 -3.1 15.3": ["niacinamide"], "-0.6 5.4 17.6": ["gina"], "2.7 18.4 8.9": ["forwardline"], "-2.0 9.9 15.4": ["ulit"], "4.4 8.1 12.9": ["streetbike"], "2.9 5.2 10.6": ["ethnocultural"], "13.4 12.0 12.5": ["kinkajous"], "3.7 26.4 3.2": ["slanderers"], "2.0 13.4 11.3": ["unpressured"], "2.9 4.9 20.9": ["salem"], "9.5 9.8 2.4": ["telesurgery"], "9.2 5.3 46.0": ["elvers"], "0.1 17.9 3.9": ["lionizes"], "17.8 13.7 28.6": ["verdigris"], "11.8 10.8 13.3": ["mentholated"], "17.1 6.0 20.1": ["biergarten"], "0.3 4.1 14.0": ["prearrange"], "1.0 6.7 6.2": ["airlink"], "13.2 16.7 25.2": ["gundog"], "10.5 5.1 13.0": ["sauciest"], "-12.5 5.5 9.4": ["subzones"], "11.7 18.5 -3.4": ["javness"], "-3.6 7.2 3.5": ["hexafluoride"], "0.6 12.5 4.3": ["parlimentary"], "13.6 -2.0 13.4": ["trousering"], "2.5 8.2 3.0": ["firesides"], "15.8 4.3 18.6": ["motherload"], "4.6 16.2 8.6": ["overdetermined"], "4.8 3.1 21.3": ["tightener"], "-4.9 4.9 10.3": ["downspacing"], "4.6 2.8 11.2": ["outworkers"], "11.0 14.2 11.4": ["socketed"], "-5.3 4.4 -0.4": ["regreted"], "19.8 9.9 7.1": ["supermassive"], "-3.5 -1.2 5.9": ["nings"], "11.4 4.9 2.2": ["profitted"], "2.6 10.5 6.1": ["retrospectivity"], "9.0 10.1 7.7": ["motorisation"], "-0.5 12.8 2.1": ["fortuity"], "7.8 13.8 11.0": ["replenishable"], "13.8 10.3 5.4": ["jokily"], "14.1 15.3 12.0": ["meditatively"], "5.4 24.6 5.9": ["codewords"], "1.4 -2.6 11.8": ["uridashi"], "9.7 25.8 11.2": ["provoker"], "6.3 9.4 16.5": ["gloveless"], "-4.3 -1.3 7.5": ["singlefamily"], "7.6 -2.8 -1.3": ["busin"], "4.3 9.7 14.7": ["asprin"], "8.2 10.3 7.6": ["rawboned"], "6.5 3.2 7.1": ["whowas"], "7.5 14.6 9.0": ["fowards"], "6.1 18.1 12.0": ["desease"], "4.3 5.3 14.5": ["camino"], "-3.7 4.1 4.1": ["tatkal"], "5.5 12.2 6.5": ["caravanserai"], "3.6 18.7 14.0": ["couplehood"], "-13.4 0.3 -0.0": ["intrapartum"], "13.0 2.1 12.9": ["claves"], "11.9 29.2 35.2": ["chigger"], "0.2 2.7 6.9": ["pointes"], "-4.6 7.4 12.9": ["vinification"], "-3.1 12.4 5.5": ["modric"], "4.4 -1.6 3.8": ["centrals"], "10.5 -2.2 18.9": ["dado"], "10.7 8.8 4.7": ["supercouple"], "1.4 28.2 15.0": ["outgroup"], "-0.8 6.3 9.7": ["energization"], "14.7 6.5 37.9": ["quenelle"], "5.2 1.0 9.7": ["kis"], "18.0 18.5 18.0": ["nailgun"], "12.1 12.3 14.5": ["tike"], "0.0 -6.8 -7.6": ["dicussed"], "10.4 5.5 8.7": ["facture"], "9.2 -0.5 7.3": ["sackfuls"], "8.5 12.3 18.7": ["bally"], "12.8 16.7 19.5": ["sfumato"], "-7.4 21.8 10.0": ["overcoach"], "10.9 22.6 10.8": ["pantywaist"], "2.7 3.0 10.0": ["negociant"], "-9.0 2.3 3.6": ["nformation"], "12.4 26.8 15.0": ["camoflauge"], "9.9 16.8 -1.9": ["pronouncedly"], "7.7 15.2 13.9": ["pashas"], "14.2 9.9 7.5": ["landbanks"], "3.9 1.4 14.8": ["araw"], "1.4 -4.3 1.4": ["xylenes"], "4.4 5.6 6.8": ["poder"], "10.7 12.2 2.5": ["techo"], "2.3 4.3 8.8": ["rootsier"], "3.2 16.0 19.2": ["calicivirus"], "10.0 6.2 7.8": ["harddrives"], "13.5 17.5 18.1": ["powerbombs"], "-0.5 8.5 13.1": ["kasama"], "6.8 17.1 19.4": ["trishul"], "6.8 6.7 15.2": ["rolex"], "-0.4 16.1 9.8": ["intermarket"], "9.4 10.6 13.4": ["hedgebook"], "2.3 2.5 4.8": ["newsreading"], "-3.7 9.4 7.9": ["muktamar"], "1.3 20.2 -1.2": ["deprogrammed"], "10.1 14.2 1.7": ["depressurizing"], "1.2 13.8 11.0": ["quotables"], "7.2 6.2 1.8": ["postprocessing"], "1.6 6.3 9.2": ["shorthander"], "9.6 6.9 10.6": ["chandra"], "0.9 14.5 9.9": ["nonmarket"], "5.6 3.6 15.3": ["grapegrowers"], "8.4 -2.7 16.8": ["texturized"], "0.4 10.1 15.7": ["xanthones"], "7.2 4.7 8.1": ["ello"], "21.7 16.7 21.4": ["snarf"], "12.8 10.7 9.8": ["futurology"], "10.7 12.3 19.5": ["dogdom"], "3.7 2.9 16.8": ["burgee"], "6.5 14.2 13.4": ["diaz"], "-1.9 14.3 6.2": ["articulateness"], "6.9 9.3 8.8": ["quencher"], "9.5 5.0 9.9": ["kumari"], "7.5 6.7 -0.2": ["coachless"], "3.2 2.9 8.1": ["formate"], "14.2 16.2 34.3": ["brachiopods"], "-3.9 19.2 2.5": ["trueness"], "0.7 13.6 12.8": ["stopcock"], "5.0 16.7 2.0": ["psychoanalyzing"], "6.6 -0.6 5.6": ["antitobacco"], "6.4 6.2 11.9": ["esto"], "1.0 16.1 -1.8": ["sametime"], "1.1 4.3 1.6": ["pharmacoepidemiology"], "0.3 9.5 9.3": ["iwth"], "-4.7 13.5 4.0": ["sero"], "14.2 6.6 10.0": ["beastiality"], "4.6 28.1 4.1": ["hajis"], "10.6 22.3 8.4": ["stoutness"], "7.7 7.8 15.7": ["quokkas"], "18.9 20.5 11.4": ["grovels"], "9.1 19.6 5.4": ["importunate"], "9.6 7.0 -1.6": ["queering"], "5.5 3.3 3.9": ["airmiles"], "7.5 -3.0 24.5": ["chowed"], "8.8 9.5 5.5": ["superinjunctions"], "2.8 14.9 7.1": ["enthalpy"], "10.6 11.0 15.8": ["earthshine"], "2.0 11.9 10.5": ["diptheria"], "9.3 1.5 3.8": ["outweight"], "23.2 2.2 11.7": ["bakelite"], "9.4 3.8 12.2": ["paleoanthropologists"], "5.2 17.0 35.3": ["driftnets"], "12.4 15.9 33.6": ["muddler"], "14.4 8.0 10.3": ["hydroforming"], "1.1 8.8 7.1": ["jamais"], "-4.2 3.1 8.6": ["mininum"], "13.4 15.7 6.5": ["hdtv"], "10.3 -4.7 16.5": ["mex"], "-1.7 21.4 5.0": ["overmanned"], "3.1 5.8 9.6": ["riads"], "5.9 1.7 0.8": ["orga"], "2.9 6.7 14.8": ["ypr"], "7.1 11.2 8.9": ["theway"], "5.6 8.5 32.7": ["dunlin"], "1.8 17.2 3.8": ["exosome"], "1.0 12.1 6.6": ["sassing"], "5.5 22.5 14.5": ["stupids"], "0.5 12.3 1.7": ["thanas"], "-6.4 1.5 6.5": ["termly"], "5.8 6.1 12.9": ["aroun"], "0.5 6.6 14.2": ["mailpiece"], "3.6 10.7 10.3": ["tactlessly"], "-2.4 1.6 -8.4": ["unrefuted"], "-6.7 12.8 7.8": ["visability"], "4.9 12.6 17.0": ["omegas"], "5.9 13.8 19.4": ["lithic"], "16.6 -0.3 13.7": ["barnlike"], "0.1 13.5 5.1": ["undertand"], "10.0 11.2 7.1": ["acquirable"], "43.4 17.9 8.7": ["megacorporations"], "-6.3 5.5 3.0": ["nonappearance"], "15.4 16.6 2.9": ["cosset"], "8.2 18.2 8.2": ["ghostbusting"], "1.6 12.1 9.7": ["aaya"], "3.8 8.6 6.2": ["kurt"], "9.9 17.0 5.6": ["cryptologists"], "0.2 14.8 11.9": ["hamare"], "-3.2 2.2 0.5": ["wheras"], "10.6 5.0 18.9": ["chil"], "0.3 10.3 3.2": ["impaneling"], "12.8 4.6 14.2": ["gobos"], "11.9 15.7 9.8": ["maneouvre"], "5.4 12.4 7.1": ["cloudiest"], "5.4 18.2 9.3": ["superheroics"], "14.4 8.5 7.6": ["eponym"], "10.4 12.5 19.8": ["solent"], "9.0 -1.4 -0.8": ["annonce"], "5.8 27.2 14.6": ["ingratiation"], "3.6 14.8 15.5": ["delaminate"], "5.8 9.4 2.7": ["outserved"], "11.2 17.2 21.0": ["conches"], "-5.7 18.6 9.4": ["milllionaire"], "5.4 7.7 24.3": ["cervid"], "-3.9 10.4 0.4": ["remandees"], "13.7 8.4 18.7": ["flagons"], "1.1 10.1 14.4": ["musclecar"], "5.7 9.7 10.4": ["overexaggerated"], "0.5 -0.6 3.5": ["registeration"], "3.9 9.8 12.0": ["senna"], "8.8 16.6 9.6": ["threeway"], "12.4 9.8 10.9": ["boudoirs"], "11.7 11.0 19.2": ["pulque"], "11.4 15.3 17.9": ["ewwww"], "1.4 20.5 7.2": ["deconstructionism"], "-1.6 13.5 4.1": ["implimented"], "-6.7 -0.2 5.4": ["neuregulin"], "6.2 14.3 7.7": ["signalmen"], "12.3 3.2 15.8": ["monica"], "-3.2 -9.5 4.7": ["compeered"], "0.7 15.8 16.5": ["mudlark"], "-0.3 4.5 7.9": ["anong"], "6.8 2.9 8.6": ["wknd"], "13.5 6.1 5.9": ["toos"], "5.6 -2.6 15.6": ["kudocast"], "20.9 13.0 11.9": ["goog"], "-2.0 5.9 1.5": ["fettled", "gulty"], "5.0 13.0 9.5": ["spatiotemporal"], "13.5 20.6 2.3": ["adulated"], "9.2 27.7 0.3": ["outmanoeuvring"], "7.3 1.6 16.7": ["ferro"], "-0.1 7.2 8.3": ["accus"], "11.4 9.1 14.8": ["boyf"], "7.0 9.0 11.5": ["rok"], "-1.4 15.1 10.6": ["linesmakers"], "7.6 11.5 3.3": ["betweenthe"], "22.6 9.3 30.0": ["booyah"], "9.6 2.2 4.6": ["chequing"], "2.8 11.8 4.7": ["plexus"], "0.8 1.5 14.8": ["forwent"], "6.7 -0.4 13.6": ["crm"], "1.8 17.1 6.4": ["loonier"], "8.4 8.6 16.9": ["jambs"], "-4.6 8.9 5.9": ["ppmv"], "16.1 22.1 15.6": ["litterally"], "2.4 9.3 9.6": ["itt"], "7.8 -2.1 22.9": ["gerbera"], "1.4 0.2 9.8": ["autre"], "0.0 11.4 0.2": ["bradykinin"], "0.4 7.0 9.2": ["subchannels"], "-0.3 8.9 17.2": ["bubbe"], "12.2 6.4 18.0": ["wheelwright"], "4.4 16.4 6.4": ["youngman"], "18.4 31.0 14.6": ["unseeing"], "9.8 7.4 7.9": ["spinnin"], "-1.7 12.1 -4.2": ["willnot"], "5.2 7.9 0.7": ["fictious"], "-6.3 13.2 10.2": ["downstaters"], "16.6 9.0 9.1": ["abandonded"], "27.8 13.0 14.2": ["uncracked"], "5.0 -1.6 3.5": ["publique"], "6.3 5.9 32.7": ["dolmas"], "10.7 6.3 13.3": ["australopithecines"], "12.1 2.8 -1.6": ["tulsa"], "12.7 11.3 16.5": ["limpness"], "7.4 14.2 7.4": ["lunacies"], "5.1 10.3 10.3": ["limonene"], "15.5 -0.3 5.9": ["ofan"], "-3.4 -3.0 16.1": ["shearlings"], "17.6 9.9 15.2": ["mallee"], "5.2 2.5 10.3": ["hypoechoic"], "0.0 3.3 1.4": ["mintue"], "3.1 13.5 16.8": ["fatale"], "22.5 14.3 5.0": ["mediascape"], "14.4 7.3 29.4": ["artisinal"], "0.1 10.5 2.4": ["weepies"], "10.9 -13.9 -6.2": ["annonced"], "8.4 12.7 6.8": ["unsoiled"], "-1.3 7.4 15.5": ["bansa"], "5.5 14.4 6.4": ["oxidiser"], "0.0 6.7 1.5": ["adi"], "-0.3 17.7 5.0": ["salah"], "5.7 5.2 9.9": ["anglais"], "12.9 8.2 14.9": ["gutteral"], "5.2 22.0 1.7": ["conjunct"], "26.0 3.8 18.5": ["gambolling"], "-6.9 -2.7 5.0": ["grandam"], "-1.2 5.3 10.9": ["innervation"], "10.8 11.6 18.5": ["freesias"], "11.2 1.6 15.9": ["underskirt"], "6.7 5.9 12.8": ["nomics"], "3.5 3.6 7.9": ["feld"], "11.4 7.9 27.8": ["nurdles"], "0.6 36.4 17.9": ["littorals"], "-1.9 23.1 10.5": ["bloodfest"], "8.5 7.2 15.3": ["jackie"], "-5.1 10.6 18.0": ["irrigational"], "-3.1 7.0 9.8": ["uniprocessor"], "4.5 7.3 8.1": ["binded"], "-4.2 -6.2 8.4": ["mimimum"], "15.3 10.9 11.3": ["kinara"], "7.1 8.2 10.6": ["unimpeachably"], "6.0 17.0 16.7": ["flattops"], "-1.2 14.5 3.6": ["browbeats"], "0.6 12.0 3.4": ["gifters"], "10.9 21.5 19.3": ["insensibility"], "10.4 36.1 12.0": ["airburst"], "7.3 6.0 10.5": ["yawners"], "3.3 18.4 8.8": ["rightie"], "9.1 1.3 5.8": ["buzziest"], "14.7 -7.3 4.5": ["ition"], "16.4 8.2 38.1": ["pattie"], "21.8 -2.6 10.6": ["entertaiment"], "16.0 15.8 25.8": ["frass"], "2.5 10.0 40.4": ["saltimbocca"], "-0.9 4.0 1.9": ["playings"], "-1.8 11.5 4.3": ["anteroposterior"], "12.8 31.6 11.6": ["horcrux"], "1.7 5.3 2.1": ["patel"], "25.4 2.5 4.6": ["supersite"], "1.0 9.5 13.8": ["jama"], "-6.2 10.9 12.7": ["thid"], "7.0 4.1 13.1": ["volumizing"], "7.2 7.7 13.2": ["perambulations"], "9.7 -5.7 12.2": ["strugging"], "13.7 4.1 4.8": ["bioelectricity"], "13.8 27.3 34.5": ["stinkbug"], "7.7 3.2 7.3": ["vn"], "-2.3 5.1 9.0": ["vibist"], "9.6 3.8 8.4": ["nymphomania"], "-1.5 12.2 7.8": ["individualities"], "11.9 12.6 30.5": ["bustards"], "-8.4 9.0 11.6": ["polypectomy"], "8.4 8.6 17.9": ["unexcavated"], "13.1 20.7 22.0": ["propellors"], "3.1 -2.0 13.2": ["duncan"], "4.9 16.9 10.0": ["underexposure"], "7.6 16.9 5.4": ["subscript"], "17.0 13.7 10.2": ["masturbator"], "6.1 -3.0 11.4": ["reseating"], "12.9 -1.2 5.0": ["strg"], "13.1 1.3 3.4": ["mcgarrybowen"], "0.6 8.3 15.3": ["silymarin"], "-6.5 12.8 10.1": ["shakhas"], "9.3 12.1 27.2": ["papaw"], "10.0 4.1 17.3": ["microbrewing"], "10.0 0.5 7.0": ["ragpicker"], "21.0 5.1 8.2": ["travelator"], "-2.0 14.3 13.4": ["karez"], "2.0 -0.8 3.5": ["intiated"], "15.3 24.1 14.1": ["peevishly"], "8.2 9.6 9.2": ["actuall"], "3.6 8.2 -2.2": ["ately"], "13.3 13.2 21.9": ["filbert"], "11.5 0.6 5.4": ["minilab"], "11.3 4.2 8.2": ["untilled"], "10.1 17.6 11.4": ["slothfulness"], "5.6 4.9 5.7": ["panchyat"], "0.7 2.3 5.0": ["tranched"], "25.6 9.0 13.5": ["roundest"], "22.7 9.2 11.2": ["chirruping"], "16.1 14.7 30.2": ["catalpa"], "9.2 16.3 21.3": ["nighthawk"], "7.3 7.0 2.3": ["soonish"], "9.6 0.7 -1.9": ["highperformance"], "20.9 8.1 8.1": ["luxo"], "4.4 15.6 12.7": ["cuckolding"], "7.9 20.2 15.2": ["materia"], "1.2 10.1 13.4": ["organoleptic"], "18.8 35.4 22.4": ["dwarven"], "6.9 0.9 9.0": ["proceding"], "2.8 11.5 14.6": ["emailwire"], "-6.0 7.9 1.2": ["highers"], "19.8 10.4 28.7": ["frizzled"], "17.1 17.0 13.8": ["biffing"], "2.2 15.2 6.4": ["bachcha"], "1.3 12.5 4.4": ["nuturing"], "6.1 12.0 13.8": ["ikke", "overconsuming"], "2.0 7.3 9.7": ["expectorants"], "21.7 7.1 18.3": ["washtubs"], "8.3 10.5 11.4": ["elliptic"], "-3.8 6.0 2.4": ["poppiest"], "15.4 12.1 7.0": ["dongas"], "9.0 11.1 10.4": ["pluckiness"], "5.0 17.6 17.5": ["solicitously"], "-9.0 9.7 -1.5": ["adumbrated"], "-3.1 10.1 0.0": ["systematizing"], "1.9 17.4 10.9": ["roaded"], "8.4 11.9 7.7": ["ethology"], "11.9 14.0 -2.5": ["dermbuilder"], "1.3 26.5 4.5": ["strenghts"], "7.8 6.2 17.8": ["ofrendas"], "4.3 37.3 8.5": ["provokers"], "-4.0 0.4 5.9": ["practicums"], "21.9 7.8 10.9": ["clopping"], "-0.2 -4.8 -7.0": ["ofice"], "1.8 21.1 14.2": ["occassionaly"], "2.7 5.0 0.4": ["steht"], "9.8 12.4 5.3": ["trib"], "24.8 21.3 12.7": ["spillcam"], "11.7 1.2 14.6": ["semifinished"], "0.4 21.8 18.2": ["overpursue"], "8.5 4.1 1.5": ["hotfooted"], "7.3 23.8 13.2": ["libtard"], "17.5 14.9 28.6": ["horsefly"], "-0.0 30.5 5.3": ["villify"], "5.9 -0.6 17.6": ["fung"], "10.5 10.6 1.7": ["neer"], "9.4 11.1 0.0": ["hardwares"], "-10.3 9.4 0.8": ["etiologic"], "6.6 24.2 7.8": ["peaces"], "-1.8 10.7 5.0": ["retransmissions"], "-8.0 8.3 8.8": ["gyno"], "25.5 31.9 17.2": ["martians"], "13.1 7.2 14.7": ["arcaded"], "-2.2 -1.2 10.4": ["cortices"], "-3.6 16.5 7.9": ["marathi"], "6.1 13.0 3.9": ["bianconeri"], "10.0 8.1 10.0": ["refranchise"], "13.2 7.7 9.3": ["knell"], "3.6 16.0 9.7": ["galli"], "9.8 4.5 0.4": ["fatfoogoo"], "7.6 -5.3 4.8": ["mdi"], "5.0 22.1 9.4": ["instancing"], "2.5 8.8 4.3": ["clubless"], "13.3 26.1 11.4": ["despotisms"], "31.6 -2.9 8.1": ["soaraway"], "-0.9 9.1 6.7": ["underachieves"], "13.4 13.1 14.7": ["paleolithic"], "-3.8 7.3 1.4": ["linewidth"], "-3.9 18.6 0.7": ["efficaciously"], "21.2 5.9 5.5": ["hotwired"], "4.6 9.3 14.5": ["logoff"], "6.4 22.6 4.0": ["morales"], "-5.0 15.6 3.1": ["propositional"], "7.7 27.9 14.9": ["outskate"], "8.5 2.3 0.2": ["mydeco"], "6.2 -7.4 3.7": ["voh"], "-1.7 11.4 5.9": ["asic"], "8.5 19.3 3.8": ["niks"], "-11.1 5.3 4.0": ["asylees"], "11.5 26.4 8.6": ["strawmen"], "-4.3 13.3 7.3": ["izzat"], "1.1 14.5 18.7": ["recontamination"], "5.8 9.6 17.4": ["albert"], "1.8 20.7 15.5": ["masculinized"], "12.0 16.2 27.0": ["chiminea"], "12.2 7.5 0.4": ["parapublic"], "3.5 10.5 -1.3": ["enthusiatic"], "5.4 18.9 14.1": ["jumpball"], "9.0 17.7 14.8": ["jaggy"], "-1.1 6.1 8.5": ["mukims"], "13.4 2.8 8.0": ["multitier"], "19.7 10.6 10.6": ["tentlike"], "11.9 9.0 7.3": ["flushers"], "-1.8 -4.4 -5.3": ["kuhl"], "-1.0 26.7 4.7": ["extraterritoriality"], "1.9 10.8 3.8": ["eyeblack"], "0.4 19.2 10.8": ["undemonstrated"], "31.1 11.6 10.7": ["superbank"], "14.0 5.3 2.2": ["bankrupcty"], "11.6 7.2 38.6": ["rouille"], "0.7 7.3 10.5": ["heterologous"], "5.8 16.8 0.2": ["resiliant"], "3.2 4.2 42.2": ["blacktip"], "5.8 8.0 14.7": ["nwanew"], "0.9 14.5 6.7": ["formational"], "3.7 5.1 1.5": ["accaept"], "0.8 3.5 17.9": ["threonine"], "3.8 11.0 3.3": ["betwee"], "16.5 4.4 27.7": ["passionflower"], "4.3 11.4 7.8": ["prosection"], "-0.3 15.3 0.3": ["mediastinum"], "11.4 11.5 18.9": ["itude"], "9.4 13.1 17.3": ["glissandi"], "1.6 10.0 2.9": ["unsearched"], "7.3 24.7 4.0": ["determinist"], "14.9 17.0 11.0": ["intrepidly"], "9.0 3.7 7.0": ["cadged"], "-4.5 12.6 2.6": ["supersectionals"], "5.0 -8.3 -3.7": ["muhn"], "8.2 20.6 19.9": ["windburn"], "1.2 25.1 1.2": ["convoying"], "3.5 15.2 7.7": ["anybodies"], "7.9 7.1 11.1": ["rooked"], "1.7 11.4 4.5": ["exciters"], "3.9 3.9 0.1": ["willcontinue"], "13.0 31.5 10.4": ["impersonally"], "-7.9 -1.1 -0.3": ["chlorpheniramine"], "5.9 5.5 1.8": ["colocate"], "-3.7 7.3 -4.0": ["achived"], "9.8 16.6 8.7": ["compulsiveness"], "16.8 15.0 16.4": ["bullwhips"], "6.2 2.9 9.1": ["multihyphenate"], "12.0 14.9 6.9": ["unspun"], "8.3 10.7 24.3": ["peccaries"], "9.5 16.5 6.3": ["thetime"], "14.6 22.0 8.1": ["stumblebum"], "3.5 7.9 12.2": ["aer"], "1.1 6.4 18.7": ["gladed"], "6.8 19.1 15.8": ["cammies"], "4.0 7.4 5.1": ["webhost"], "16.8 10.0 7.9": ["freefalls"], "-8.3 3.0 1.7": ["scord"], "16.7 14.3 14.8": ["razorblade"], "7.9 -2.2 6.1": ["erin"], "-4.2 25.1 14.5": ["pararescue"], "-5.0 7.9 9.8": ["outbracket"], "11.5 9.7 19.6": ["fussbudget"], "7.9 19.2 8.5": ["poxviruses"], "0.8 5.1 11.5": ["wesley"], "7.1 16.8 4.9": ["noncooperative"], "2.8 21.4 15.3": ["camraderie"], "1.2 5.5 4.8": ["dehumidify"], "10.5 10.7 8.1": ["exer"], "14.2 21.9 12.6": ["shapeshifters"], "8.0 11.8 21.2": ["eyespots"], "7.0 8.9 8.0": ["chondrites"], "12.6 12.8 29.6": ["dinoflagellate"], "8.3 21.2 7.2": ["kleptocracies"], "11.1 13.5 18.8": ["kickboard"], "9.0 3.8 29.2": ["rioja"], "15.5 13.3 48.9": ["pelagics"], "12.7 10.9 10.2": ["overdramatized"], "-0.4 14.8 0.4": ["tosee"], "20.7 21.6 9.9": ["superheat"], "11.0 17.5 8.1": ["unbootable"], "1.4 13.8 2.3": ["subsectional"], "8.2 -1.1 15.5": ["cele"], "5.2 7.6 10.8": ["rockiness"], "0.7 2.2 12.9": ["gis"], "20.8 18.5 9.7": ["klutzes"], "5.2 11.6 6.3": ["amn"], "3.6 10.9 6.0": ["supersports"], "9.3 0.4 -3.5": ["towork"], "17.0 13.1 8.5": ["oustide"], "5.0 9.9 6.4": ["toothlessness"], "11.6 11.5 2.1": ["reincarnates"], "7.1 5.6 -4.5": ["signagelive"], "-0.9 4.4 10.2": ["gangue"], "5.3 8.7 11.6": ["ravel"], "1.3 3.2 6.8": ["habe"], "2.7 3.4 9.6": ["mazurkas"], "7.9 15.1 23.7": ["pinyon"], "4.6 13.7 9.2": ["theis"], "-0.5 1.3 1.8": ["railcard"], "-11.8 16.8 -2.7": ["dialogic"], "3.6 28.5 4.0": ["counterrorism"], "8.6 2.6 5.3": ["biotherapy"], "2.8 16.3 6.5": ["hink"], "4.0 0.0 11.8": ["viaticals"], "-5.2 -1.3 6.5": ["coproducts"], "7.8 7.6 8.2": ["dhamaka"], "7.2 5.6 9.6": ["fridays"], "1.7 6.1 5.0": ["kirtans"], "3.3 -1.9 19.2": ["fais"], "-3.9 6.2 6.8": ["tocontinue"], "4.4 -3.3 9.2": ["chaque"], "7.5 15.2 11.6": ["aggies"], "6.3 14.1 12.8": ["phylacteries"], "-0.5 18.8 6.6": ["calibur"], "17.4 3.8 12.1": ["utube"], "-3.4 6.2 7.2": ["homegoing"], "-0.1 7.5 11.6": ["shabbat"], "7.3 11.3 7.4": ["stemwinder"], "7.4 6.3 3.5": ["supervoting"], "8.3 13.4 1.2": ["unsucessful"], "1.1 5.7 6.8": ["cmdlets"], "-3.9 9.1 4.3": ["turndowns"], "-9.5 6.7 10.8": ["reforecast"], "-0.2 1.4 9.3": ["chartbusting"], "9.1 16.0 11.6": ["inoffensively"], "11.6 15.2 15.8": ["maulers"], "-1.5 24.4 5.0": ["demoralises"], "-1.8 10.8 3.2": ["hydrologically"], "14.4 1.6 10.0": ["bosomed"], "2.0 11.5 1.4": ["wuld"], "1.0 -2.0 8.7": ["rediscounting"], "-0.7 10.7 10.7": ["rahe"], "0.1 1.3 4.4": ["schoolwear"], "12.4 1.1 8.2": ["grazie"], "9.3 6.6 9.4": ["sadsack"], "6.5 5.5 -1.5": ["unusally"], "4.1 13.1 5.1": ["karta"], "6.4 16.6 7.8": ["somnambulism"], "7.4 2.1 3.9": ["hcl"], "-7.4 13.7 8.7": ["antipyretic"], "8.8 1.8 18.3": ["wristlets"], "4.0 11.3 -6.6": ["fundemental"], "3.2 10.0 16.6": ["demurral"], "8.4 3.8 -11.3": ["comissioned"], "14.3 19.1 18.7": ["bolos"], "-2.3 3.5 9.3": ["ministrokes"], "14.4 17.2 10.2": ["overoptimism"], "7.6 16.5 16.9": ["vigorish"], "12.5 12.7 8.5": ["confoundingly"], "12.5 24.0 19.3": ["rapscallions"], "0.9 6.7 1.8": ["peakers"], "2.7 16.0 1.4": ["familly"], "8.4 2.3 13.3": ["roon"], "-0.7 10.5 14.5": ["localness"], "18.9 16.4 11.9": ["oculus"], "2.2 -0.8 1.6": ["nothwithstanding"], "-4.5 -2.7 9.6": ["reimplantation"], "3.8 0.2 14.3": ["arboricultural"], "20.3 26.6 28.1": ["mateys"], "-1.3 7.2 7.4": ["palmitate"], "-10.8 -7.4 3.4": ["attened"], "8.9 13.1 10.7": ["grannie"], "9.9 12.4 10.5": ["caret"], "-7.7 4.0 6.4": ["siyempre"], "6.3 2.5 13.5": ["backhauls"], "-11.9 4.2 2.4": ["classmen"], "-2.9 6.4 6.6": ["weightages"], "3.6 2.5 -7.5": ["newsconference"], "-5.5 -3.8 -0.0": ["codirected"], "4.2 -1.9 0.8": ["telluride"], "-12.5 16.4 1.3": ["hafiz"], "12.0 1.6 14.7": ["gilds"], "2.0 12.8 0.1": ["hermitages"], "0.7 -2.3 3.6": ["offtakers"], "11.4 5.5 2.4": ["gibt"], "-1.4 11.8 8.3": ["realizability"], "-8.0 0.8 0.2": ["sulfatase"], "16.0 23.3 17.1": ["younglings"], "0.5 16.8 15.9": ["tweeze"], "-2.5 3.2 5.6": ["ileus"], "1.4 7.3 12.7": ["relitigation"], "-3.1 8.1 9.6": ["selfesteem"], "-4.9 21.7 2.1": ["equivocally"], "7.7 20.6 -3.8": ["necklacing"], "-3.4 11.0 8.0": ["nematicide"], "-3.1 -3.3 2.9": ["gerontological"], "11.1 3.3 16.4": ["fauxhawk"], "0.0 6.0 -6.5": ["rediff"], "8.4 25.3 10.5": ["shithead"], "-5.3 -0.7 10.3": ["cytological"], "24.3 15.4 10.7": ["gameboard"], "16.7 15.4 20.0": ["underwing"], "9.7 1.5 4.8": ["nonretail"], "9.9 10.7 15.3": ["snicking"], "6.0 -1.2 16.8": ["thalassotherapy"], "3.9 -6.0 21.4": ["suckler"], "1.7 8.3 -2.8": ["responsbile"], "7.3 24.3 9.6": ["fatalistically"], "20.8 20.3 16.7": ["pinwheeling"], "7.4 17.8 1.7": ["synergised"], "6.2 12.5 8.2": ["pompousness"], "4.8 2.1 6.0": ["ool"], "-9.1 1.0 -6.2": ["smc"], "7.6 13.2 9.1": ["netcord"], "13.1 9.3 18.2": ["lushes"], "10.2 5.0 10.5": ["penstocks"], "6.5 19.4 11.4": ["fovea"], "-1.6 0.7 1.6": ["unatt"], "3.4 25.8 9.9": ["predesignated"], "16.9 5.3 15.2": ["socko"], "14.3 5.2 12.7": ["stilettoes", "masive"], "6.2 2.5 6.5": ["becauseof"], "-8.1 4.8 1.6": ["canonic"], "-0.7 6.9 15.7": ["silvicultural"], "10.8 3.8 29.7": ["ube"], "8.0 5.6 47.9": ["eider"], "-2.0 1.9 5.6": ["yhe"], "17.4 16.4 3.4": ["guardhouses"], "11.3 14.6 20.8": ["serpentinite"], "-2.6 7.2 1.9": ["peccadillos"], "10.0 4.1 10.1": ["guayule"], "19.7 9.5 14.8": ["teet"], "2.2 6.3 9.7": ["theother"], "-2.8 13.7 1.1": ["depoliticizing"], "-4.0 9.2 -0.8": ["totheir"], "-1.3 12.6 12.5": ["adlib"], "6.5 5.7 6.1": ["headtracking"], "2.1 6.2 10.1": ["fluorescein"], "-1.6 14.9 8.6": ["psychodramas"], "2.3 9.1 10.4": ["oleocanthal", "unforecasted"], "5.2 17.0 -4.3": ["irrelevantly"], "16.0 33.2 12.5": ["ninjutsu"], "2.3 2.6 -2.6": ["developes"], "2.3 7.9 -2.0": ["paysafecard"], "5.7 4.7 8.6": ["twistier"], "9.0 10.4 23.1": ["sumthin"], "-1.1 7.2 7.1": ["overbreadth"], "7.1 7.9 9.0": ["mudfest"], "-10.8 3.6 1.2": ["tehsildars"], "0.6 11.4 5.6": ["karan"], "12.6 -1.4 4.0": ["minutos"], "16.7 6.8 9.6": ["tromps"], "-4.2 5.1 7.4": ["noncovered"], "6.2 1.7 11.8": ["kickstands"], "17.2 11.1 1.1": ["rotundas"], "3.4 11.5 8.0": ["lyk"], "-0.1 12.5 -4.2": ["misappropriates"], "15.9 7.0 -1.5": ["disintermediated"], "7.0 17.3 10.2": ["disillusions"], "-7.0 8.5 12.1": ["reevaluations"], "-0.6 7.7 12.6": ["palpated"], "6.6 5.6 16.4": ["structurals"], "-3.7 5.1 16.0": ["vinified"], "13.4 5.7 -3.1": ["ballyhooing"], "10.1 4.2 5.6": ["scintillator"], "13.7 3.1 36.7": ["bibingka"], "17.0 9.3 14.2": ["scrounges"], "17.1 -0.6 16.7": ["frothier"], "10.8 15.4 12.7": ["eyeblink"], "4.5 7.8 16.0": ["shadowboxes"], "-4.2 8.7 5.7": ["gearchanges"], "-0.5 11.5 2.8": ["rekey"], "19.7 10.4 15.7": ["microdot"], "8.0 -0.3 7.0": ["triaxial"], "12.1 7.6 12.6": ["thise"], "7.2 5.7 -1.4": ["dramatisations"], "6.3 1.1 15.5": ["oligosaccharide"], "1.0 3.6 4.4": ["alkenes"], "5.4 13.0 6.3": ["abilityto"], "0.9 8.7 10.2": ["outdug"], "2.4 6.4 -2.5": ["jubilated"], "4.0 -0.1 5.6": ["danoprevir"], "3.1 -10.9 -6.4": ["overviewed"], "8.9 3.5 18.1": ["wate"], "7.2 8.4 19.9": ["fixies"], "8.5 10.2 10.7": ["partie"], "0.8 8.9 13.4": ["caringly"], "-4.6 9.6 7.2": ["grayshirting"], "1.0 5.9 6.6": ["overriden"], "3.9 7.5 10.6": ["ouds"], "5.0 19.5 7.0": ["rascist"], "10.2 1.8 1.7": ["ising"], "6.0 5.5 15.0": ["rosso"], "4.9 14.6 27.1": ["ricefields"], "4.0 15.8 1.6": ["kibbutznik"], "0.8 11.6 1.9": ["jetzt"], "7.2 6.0 41.4": ["spaghettini"], "4.2 11.0 0.5": ["ownable"], "-1.8 -1.4 1.6": ["dialyzer"], "5.4 7.1 5.9": ["uninstalls"], "4.2 4.5 13.5": ["oleoresins"], "9.2 11.6 33.1": ["tomalley"], "6.9 5.3 8.4": ["powershell"], "7.1 8.2 10.1": ["chloropicrin"], "-0.8 4.9 7.4": ["nonclassical"], "10.9 15.6 6.2": ["mobilephone"], "-3.3 9.1 10.5": ["comingling"], "13.3 2.0 13.5": ["recoat"], "3.5 6.5 23.8": ["kenkey"], "3.3 6.8 11.1": ["diflucan"], "5.5 8.0 21.3": ["pato"], "5.5 8.0 16.6": ["dewormer"], "19.7 8.2 27.1": ["totara"], "13.3 21.8 9.9": ["untrainable"], "3.6 3.8 14.2": ["archaelogical"], "8.7 13.1 18.4": ["cindy"], "-2.2 9.1 4.4": ["setpoints"], "2.5 7.8 5.1": ["backtested"], "25.1 12.9 16.1": ["plushies"], "10.4 7.6 7.3": ["scrivener"], "4.1 6.0 6.5": ["palmist"], "20.7 2.2 8.8": ["flipbooks"], "3.0 3.3 4.9": ["confi"], "-3.1 -2.5 11.2": ["songlist"], "5.4 9.0 11.6": ["germinal"], "2.8 -0.2 16.8": ["snowtubing"], "12.1 13.9 5.5": ["cleansings"], "10.8 30.4 17.4": ["unsheathe"], "9.8 -1.8 7.4": ["toute"], "10.8 0.1 -1.4": ["minilabs"], "14.5 9.1 20.5": ["trunnion"], "17.8 14.3 14.5": ["alack"], "-4.7 18.1 6.8": ["verbalizes"], "-10.0 13.1 7.4": ["imipenem"], "10.9 2.5 13.8": ["bellyaches"], "7.2 19.5 -2.3": ["gullibly"], "9.6 9.7 35.9": ["pinniped"], "-2.8 10.6 12.3": ["pollworker"], "14.3 -7.8 8.1": ["ahed"], "-6.8 15.9 4.8": ["arenot"], "20.7 5.1 14.0": ["centime"], "7.4 9.2 -0.7": ["innovatory"], "-7.8 15.1 1.2": ["entireties"], "0.9 0.2 3.0": ["betweem"], "6.9 10.0 13.4": ["nough"], "8.8 35.8 20.7": ["bowmen"], "5.2 -6.4 -7.2": ["accoding"], "3.5 6.4 -1.5": ["orated"], "3.3 1.5 10.3": ["nanoimprint"], "-1.8 11.9 14.0": ["intraconference"], "10.3 11.3 9.2": ["scrappily"], "0.5 2.2 13.4": ["wagerers"], "-1.9 1.1 3.5": ["flowable"], "10.4 9.7 19.0": ["photobioreactors"], "5.1 22.3 9.1": ["reification"], "2.8 11.0 21.9": ["euphorbias"], "6.7 14.0 8.6": ["pipedreams"], "17.6 -8.9 30.2": ["riblets"], "-7.5 -1.9 -2.4": ["drs"], "0.1 2.2 6.2": ["neurogenetics"], "10.1 3.5 4.1": ["obsoleted"], "9.3 11.9 9.3": ["clerestory"], "7.0 10.1 22.7": ["birdwatch"], "12.8 15.9 13.6": ["dowsers"], "7.1 9.7 29.0": ["redd"], "16.6 7.0 1.2": ["starchitects"], "11.1 4.0 14.0": ["ovo"], "6.2 6.0 31.5": ["kales"], "11.1 10.8 4.4": ["impulsion"], "0.2 9.9 12.2": ["seth"], "8.1 12.0 15.2": ["dogbreath"], "0.1 18.6 -1.0": ["heil"], "1.3 4.5 2.1": ["reargued"], "11.7 13.8 12.2": ["flamethrowing"], "2.5 -2.0 19.7": ["napa"], "11.2 3.5 11.3": ["reminscent"], "9.2 -0.1 17.7": ["kini"], "7.4 2.2 10.2": ["meadowland"], "11.5 17.7 7.6": ["credulously"], "9.5 9.4 8.9": ["whimsicality"], "-1.8 14.7 14.4": ["chaseable"], "1.2 4.5 2.4": ["headcoach"], "-0.6 5.0 -1.2": ["hydrides"], "-8.3 -0.7 4.0": ["orthopaedist"], "1.3 15.7 7.3": ["controllables"], "9.1 21.2 14.1": ["numerators"], "8.2 12.5 13.7": ["smarminess"], "27.1 9.4 13.4": ["whirly"], "7.1 10.3 12.3": ["akharas"], "1.0 1.0 2.5": ["sbe"], "9.1 7.5 14.3": ["arcuate"], "2.2 14.3 3.4": ["cleanskins"], "-0.9 19.4 10.1": ["corrosiveness"], "1.5 -1.1 13.5": ["magandang"], "15.3 17.5 13.9": ["voraciousness"], "10.6 6.6 5.0": ["coachbuilders"], "8.2 -0.5 2.1": ["tomhimpe"], "4.8 8.3 12.4": ["cilium"], "7.7 8.1 16.2": ["mechanise"], "9.0 14.9 12.3": ["peptoids"], "7.1 4.4 -2.8": ["modernisations"], "11.7 4.9 13.2": ["quaffs"], "-4.1 17.4 -6.4": ["persued"], "-14.8 8.1 0.3": ["citable"], "12.1 12.4 15.4": ["unstrung"], "-2.1 5.3 7.8": ["altiplano"], "11.1 10.8 5.3": ["unsynchronized"], "13.3 15.5 8.3": ["dicked"], "6.5 9.0 8.2": ["suaveness"], "10.8 1.5 26.5": ["pina"], "2.1 10.5 6.9": ["nanomedicines"], "23.5 15.7 10.9": ["holograph"], "13.6 8.4 14.5": ["bucky"], "2.2 0.9 19.1": ["cutwork"], "11.9 20.4 24.3": ["seacraft"], "0.7 10.8 12.0": ["fema"], "1.8 17.7 -2.5": ["absorbtion"], "-0.6 18.1 17.0": ["tanod"], "7.8 12.9 0.6": ["topranked"], "3.3 10.5 9.6": ["wip"], "1.4 12.6 -1.4": ["amr"], "6.5 6.8 -12.3": ["infringment"], "12.6 7.5 7.5": ["pentium"], "10.6 17.5 8.2": ["smishing"], "3.8 7.6 7.9": ["uremia"], "-5.7 9.4 2.8": ["ccc"], "10.7 5.4 -0.3": ["mktg"], "18.5 17.5 15.3": ["moshers"], "3.0 1.9 -3.0": ["nationa"], "6.3 13.0 11.8": ["overregulate"], "5.4 22.0 7.6": ["firefront"], "-0.8 9.3 27.5": ["haor"], "16.2 2.2 9.4": ["grunty"], "3.3 -3.9 5.6": ["cumene"], "13.8 4.4 3.6": ["spunbond"], "4.3 7.9 5.8": ["churchwomen"], "2.3 5.9 11.6": ["galanin"], "-0.6 4.3 9.2": ["neomycin"], "19.8 3.2 24.9": ["ticklers"], "3.9 12.0 18.4": ["lateritic"], "1.6 1.8 12.1": ["labial"], "0.7 8.5 11.8": ["microlitre"], "-2.2 12.1 6.4": ["dhamma"], "-2.5 12.8 4.0": ["uncorrectable"], "27.0 12.6 22.9": ["fishbowls"], "-8.0 -6.0 1.9": ["tary"], "10.8 -2.5 30.9": ["potpies"], "5.3 21.0 12.2": ["courtliness"], "9.8 16.6 10.7": ["neurone"], "9.1 12.2 7.4": ["knottiest"], "11.7 20.4 33.0": ["chucklehead"], "6.6 13.1 4.0": ["videophile"], "7.5 12.7 8.8": ["thane"], "-0.8 9.7 -0.8": ["iotum"], "10.2 10.2 12.1": ["charwoman"], "1.5 15.1 1.8": ["romanticist"], "12.3 13.5 10.0": ["overexuberance"], "7.7 12.1 11.2": ["narky"], "-0.4 3.1 11.5": ["allkpop"], "-0.5 20.7 -5.4": ["empathically"], "-4.0 13.7 -2.7": ["interpretor"], "2.1 14.5 21.3": ["lodgepoles"], "-5.2 4.0 0.6": ["concurrences"], "13.4 8.7 11.1": ["boozehound"], "5.0 7.5 3.9": ["rember"], "9.3 14.0 4.9": ["modernly"], "7.6 16.2 -5.7": ["suborning"], "-7.3 23.6 6.5": ["paleoconservative"], "18.5 10.7 17.3": ["scuzz"], "3.6 12.5 13.7": ["nephrons"], "13.1 14.8 13.5": ["dognapped"], "17.6 2.6 22.1": ["diabolo"], "2.5 13.4 9.2": ["shanti"], "5.2 9.3 8.1": ["needleless"], "13.9 0.9 14.7": ["pes"], "5.8 18.6 20.3": ["hangul"], "-0.3 28.1 2.8": ["delegitimizes"], "5.4 21.3 13.2": ["lovability"], "-1.6 17.7 9.6": ["epigraphs"], "10.7 13.0 16.2": ["iceburg"], "7.9 -3.1 4.8": ["highlevel"], "-2.8 -0.6 8.9": ["acetonitrile"], "0.2 19.5 1.5": ["lossing"], "-1.6 11.2 13.5": ["ultramarathoner"], "-1.1 22.0 8.4": ["unidimensional"], "6.0 24.4 7.2": ["polticians"], "11.4 7.2 16.6": ["wroth"], "0.3 -1.6 3.8": ["vildagliptin"], "-3.9 15.3 3.7": ["officiers"], "13.6 9.5 12.6": ["penumbral"], "9.1 -4.9 0.8": ["xinhuanet"], "10.0 11.7 4.7": ["dafter"], "-4.3 4.9 19.5": ["cohesin"], "-5.6 5.5 0.9": ["extracranial"], "7.8 1.1 2.1": ["gastroscopy"], "7.6 13.9 17.7": ["knowin"], "1.4 10.6 6.9": ["samaritan"], "2.8 12.9 0.9": ["welch"], "8.3 11.7 5.9": ["backpost"], "7.9 10.9 14.6": ["snowriders"], "22.2 4.2 22.9": ["mcdonalds"], "1.6 4.3 6.9": ["cordsets"], "6.9 27.9 8.6": ["implacability"], "-0.8 20.2 -2.6": ["undeviating"], "13.6 13.5 13.5": ["tabard"], "3.1 5.6 9.4": ["powell"], "8.7 2.4 10.7": ["amylin"], "16.1 1.9 4.0": ["marketperform"], "0.8 -1.6 8.8": ["cementless"], "2.1 -12.1 -0.7": ["owever"], "20.8 1.7 4.5": ["bodged"], "11.8 10.8 -4.9": ["dtp"], "7.9 3.7 18.2": ["longyi"], "-2.3 -0.5 2.0": ["secretarygeneral"], "10.2 11.7 35.6": ["firetiger"], "5.0 8.5 19.3": ["simulative"], "2.5 15.3 3.7": ["divulgence"], "1.8 8.7 8.6": ["nill"], "2.6 -7.2 -3.0": ["responsed"], "9.9 26.3 7.8": ["legionaries"], "27.3 30.2 24.8": ["basilisk"], "4.8 3.9 10.2": ["coanchor"], "6.7 17.1 21.1": ["gutshot"], "11.5 7.2 20.0": ["fruitflies"], "-6.1 44.7 11.6": ["irreconcilables"], "2.5 1.5 -0.2": ["uclick"], "13.5 15.2 6.3": ["reich"], "0.0 13.2 3.6": ["unaccessible"], "5.5 9.5 18.0": ["obvi"], "1.2 10.1 -1.4": ["nonpunitive"], "5.1 -3.8 -0.8": ["employeed"], "3.8 3.3 -4.0": ["nand"], "9.3 11.6 15.0": ["hurleys"], "-4.7 8.7 12.2": ["wresters"], "10.9 0.9 -3.2": ["atomizers"], "12.3 7.2 0.2": ["mindbending"], "-2.6 5.8 16.6": ["blastomycosis"], "18.6 19.1 14.0": ["hightails"], "5.7 4.6 7.6": ["freecycling"], "6.6 10.1 3.9": ["entrain"], "15.6 12.3 25.1": ["shrimpy"], "7.6 2.3 16.3": ["multimonth"], "1.5 16.4 5.7": ["chelate"], "9.1 14.9 6.0": ["endemically"], "14.4 -0.3 -2.8": ["firstever"], "13.0 24.6 23.7": ["twitcher"], "0.5 4.6 9.0": ["waterwise"], "12.8 15.4 14.0": ["steadicam"], "13.5 14.7 14.5": ["narf"], "9.8 7.8 -0.6": ["bigged"], "12.6 12.3 22.1": ["schnozz"], "10.0 16.5 45.2": ["brookie"], "11.3 12.8 19.1": ["checkstand"], "4.0 2.8 7.3": ["monthold"], "-0.2 4.7 1.2": ["medicalisation"], "-3.8 11.3 5.2": ["studiedly"], "11.7 4.1 4.2": ["panasonic"], "3.2 8.8 2.9": ["extratime"], "-11.1 3.9 5.2": ["subtyping"], "10.9 -0.2 -8.2": ["lifepr"], "9.1 1.2 14.0": ["pentachlorophenol"], "6.9 -0.4 26.1": ["cheesemonger"], "20.4 10.3 24.3": ["masticating"], "17.4 9.2 0.2": ["posterchild"], "5.4 2.4 -1.4": ["tosupport"], "9.4 1.7 15.6": ["flaxen"], "-6.3 19.3 5.6": ["servicepersons"], "-2.2 -0.1 -1.8": ["lodgments"], "13.5 5.1 24.8": ["netsuke"], "-4.0 15.0 6.0": ["disingenous"], "12.2 2.7 3.2": ["bande"], "10.9 16.4 6.8": ["unentertaining"], "11.2 2.3 2.5": ["propects"], "4.5 1.2 0.6": ["foll"], "3.7 2.0 0.2": ["inves"], "4.7 17.1 6.3": ["beit"], "2.9 2.2 3.9": ["versitile"], "10.6 15.5 18.7": ["festiveness", "nurdling"], "8.0 -5.4 3.7": ["tras"], "7.2 3.3 13.8": ["progs"], "9.7 6.3 27.3": ["crunchies"], "21.8 16.6 16.7": ["rainclouds"], "14.5 15.2 31.6": ["pileated"], "-8.5 9.0 14.1": ["recapper"], "16.4 8.7 29.3": ["saddleback"], "15.8 9.9 16.4": ["fifes"], "15.5 21.5 22.3": ["catbird"], "0.9 14.1 16.8": ["grindin"], "0.6 0.7 10.4": ["quand"], "6.7 8.0 11.1": ["balladeering"], "-6.8 -6.7 5.3": ["wehl"], "11.5 27.8 10.1": ["unamerican"], "6.8 10.2 -2.0": ["abondoned"], "-6.2 7.2 -0.9": ["mitomycin"], "0.5 7.7 12.0": ["rheological"], "17.6 12.3 27.4": ["shorebreak"], "7.8 1.0 9.8": ["varios"], "4.1 12.4 22.7": ["overate"], "12.6 11.8 14.0": ["slappy"], "2.7 7.2 11.2": ["nitch"], "6.4 10.3 6.5": ["handpump"], "-2.9 9.2 9.8": ["folliculitis"], "3.0 13.4 3.0": ["innacurate"], "2.5 5.7 -0.4": ["tz"], "7.7 7.1 13.9": ["clubbies"], "0.7 2.5 3.7": ["viscometer"], "9.9 8.1 13.2": ["phosphorite"], "2.1 6.1 10.7": ["vimentin"], "-6.1 -0.6 3.6": ["aimag"], "3.6 18.8 16.6": ["chartplotter"], "6.1 -1.0 3.2": ["seront"], "16.0 11.7 26.6": ["derbys"], "-1.9 6.8 14.2": ["psoriatic"], "-3.7 -2.1 30.0": ["hogget"], "-1.1 6.8 10.4": ["folkier"], "0.2 5.9 13.1": ["diana"], "6.2 2.9 20.2": ["capesizes"], "12.4 12.7 8.4": ["ectomy"], "5.1 22.6 14.8": ["danes"], "1.3 6.5 12.8": ["glomerular"], "12.6 5.2 10.7": ["oldish"], "17.5 14.2 27.1": ["broils"], "11.4 7.8 11.9": ["gusseted"], "2.8 -6.6 4.8": ["chek"], "4.4 -3.1 5.0": ["quire"], "6.4 3.2 14.9": ["donne"], "5.5 -0.1 18.3": ["asphalts"], "2.6 4.8 0.3": ["subrogated"], "9.5 28.1 6.5": ["jingoists"], "11.2 17.4 25.6": ["catchin"], "3.9 19.7 14.5": ["flintlocks"], "13.0 3.5 4.5": ["majo"], "6.5 13.3 11.3": ["chengguan"], "8.3 3.8 35.4": ["mangosteens"], "8.2 8.5 -2.4": ["rubicon"], "-2.3 8.3 9.0": ["condtions"], "9.8 14.7 24.2": ["blued"], "4.1 36.8 4.2": ["psywar"], "12.3 12.4 43.8": ["quenelles"], "13.6 21.9 19.9": ["hatchway"], "3.3 3.4 -4.9": ["dmexco"], "1.6 9.7 13.7": ["lankier"], "3.8 12.9 15.9": ["copasetic"], "16.3 15.3 38.8": ["americanus"], "7.8 7.2 36.7": ["oversalted"], "18.8 13.7 30.9": ["muntjac"], "-0.3 7.1 6.2": ["triphosphate"], "4.4 -10.0 12.5": ["hgh"], "3.9 33.5 5.7": ["axiomatically"], "-2.2 3.0 -0.3": ["reservationless"], "4.4 17.3 11.6": ["mmo"], "15.9 24.4 15.4": ["stabby"], "6.8 7.4 14.0": ["volcaniclastic"], "-0.4 2.7 -0.1": ["webchats"], "1.0 -8.1 5.7": ["reapproval"], "4.7 4.9 24.7": ["mirchi"], "-2.6 4.7 44.7": ["gillnetting"], "12.8 14.3 14.0": ["sillies"], "3.3 13.2 20.1": ["pasturage"], "13.6 -5.3 11.0": ["boxloads"], "-1.8 15.4 10.2": ["neovascular"], "8.7 10.4 13.4": ["goodish"], "7.6 -2.2 27.2": ["farmstands"], "6.8 14.6 9.0": ["unflaggingly"], "1.6 8.0 2.3": ["tworun"], "6.5 7.3 28.4": ["alpines"], "1.5 7.9 3.9": ["indefiniteness"], "7.6 3.1 6.0": ["conservers"], "6.6 4.3 9.3": ["styler"], "10.1 7.4 29.3": ["bronzy"], "14.9 7.9 2.5": ["unoffical"], "15.8 5.0 13.6": ["engorge"], "-6.9 10.1 0.4": ["osmolarity"], "18.2 20.5 7.2": ["populus"], "2.1 -4.7 -0.3": ["pvs"], "4.1 4.6 0.2": ["gdgt"], "-3.3 1.9 12.6": ["receivals"], "8.3 17.1 13.2": ["broodingly"], "2.1 8.8 10.6": ["reprioritising"], "15.1 10.1 8.5": ["laggers"], "0.5 -0.9 8.0": ["cdn"], "8.9 2.5 30.9": ["hotdish"], "7.7 11.4 10.9": ["bacteriostatic", "boink"], "8.4 3.3 2.9": ["micromechanical"], "6.7 17.0 12.0": ["lifestream"], "11.5 11.1 14.0": ["annus"], "4.5 15.7 8.0": ["nightside"], "12.2 6.9 5.3": ["electroluminescence"], "7.4 5.3 2.6": ["baord"], "5.0 8.2 2.1": ["cahoot"], "-7.4 1.8 4.3": ["coinfection"], "18.0 19.2 26.0": ["abyssal"], "-5.6 12.3 2.2": ["thirdhand"], "12.0 4.4 6.2": ["punned"], "4.0 -0.2 7.5": ["carburetion"], "13.6 5.3 5.1": ["flam"], "15.5 -3.3 11.5": ["showbag"], "5.6 9.4 4.4": ["neighbored"], "14.3 16.0 3.4": ["antiglobalization"], "10.0 26.9 5.0": ["fuhrer"], "15.9 15.9 27.0": ["deadheads"], "-1.8 5.9 7.9": ["nea"], "2.5 0.9 8.3": ["hote"], "5.5 5.4 31.0": ["aquacultural"], "-1.4 11.0 11.7": ["blackburn"], "9.2 4.9 14.0": ["cro"], "20.7 17.0 23.0": ["scarabs"], "2.9 0.2 17.6": ["paddlesports"], "8.7 11.5 12.2": ["lugnut"], "5.1 5.4 4.0": ["signifigant"], "-1.0 14.3 1.9": ["polygrapher"], "9.7 8.4 5.7": ["reinstalls"], "-11.8 12.9 0.2": ["reconstructionists"], "-1.7 18.1 0.8": ["suppossed"], "9.7 23.1 10.0": ["witchhunts"], "6.2 19.3 5.4": ["ingenuously"], "4.8 7.0 16.6": ["motu"], "15.7 8.6 13.9": ["gabbling"], "4.0 7.1 -10.3": ["critisised"], "8.7 21.4 6.2": ["cyberdefense"], "5.4 16.7 8.9": ["roomfuls"], "17.4 0.8 1.4": ["ndia"], "2.2 1.7 14.4": ["jie"], "8.2 8.9 5.8": ["cutomers"], "-1.7 12.6 11.9": ["mintmark"], "2.9 -2.5 -0.2": ["joyed"], "2.5 16.5 -1.4": ["manyfold"], "14.4 3.8 6.2": ["reinjecting"], "12.6 15.7 26.9": ["concretion"], "12.6 17.5 7.1": ["fetishizes"], "9.2 7.5 0.6": ["queing"], "22.0 3.0 8.3": ["distie"], "4.7 -2.6 5.9": ["ero"], "-0.3 -1.8 1.7": ["elinogrel"], "14.5 25.4 2.7": ["weaponise"], "11.7 8.2 19.1": ["bathmat"], "-1.3 1.6 5.7": ["bre"], "3.4 1.8 6.8": ["skirtings"], "7.9 19.5 23.5": ["hibernators"], "4.9 15.4 12.5": ["pons"], "-6.4 5.7 9.0": ["explants"], "22.4 27.4 14.1": ["spidey"], "7.3 -4.6 3.3": ["metallocene"], "7.2 30.2 0.7": ["propagandas"], "6.4 19.3 4.7": ["factitious"], "11.8 -0.9 20.8": ["chignons"], "6.6 10.5 12.1": ["diego"], "14.5 11.1 21.0": ["baldies"], "-1.5 -4.0 5.8": ["smb"], "6.5 9.2 7.0": ["ingly"], "2.4 6.9 6.1": ["chargemaster"], "9.8 4.0 40.2": ["cracklings"], "4.3 3.0 4.0": ["genic"], "3.2 9.2 10.0": ["bullriders"], "2.8 0.0 5.9": ["pregancy"], "16.2 13.8 13.5": ["skidders"], "-2.4 1.9 7.0": ["berger"], "7.7 9.3 21.0": ["sheller"], "9.8 12.9 6.1": ["soccered"], "9.0 5.3 10.2": ["doubledigit"], "8.6 38.3 -0.3": ["mujahideens"], "-0.3 14.8 -1.7": ["surrending"], "6.3 4.7 25.7": ["localvore"], "-6.2 13.0 -2.2": ["gutlessly"], "-3.3 13.1 19.2": ["drydockings"], "4.4 4.6 13.1": ["heelers"], "11.5 16.3 26.5": ["anoles"], "1.4 3.2 3.8": ["disulfide"], "1.5 12.7 21.8": ["snowmachining"], "6.9 4.1 7.4": ["theprevious"], "10.6 19.7 12.8": ["unforgivingly"], "3.5 -3.3 4.5": ["healt"], "3.2 11.3 18.1": ["nevus"], "6.1 5.6 -1.3": ["furnishers"], "1.8 20.2 3.3": ["humanises"], "-0.7 6.8 7.0": ["trichloroethene"], "7.6 5.8 1.1": ["ife"], "-2.8 9.8 3.1": ["pune"], "11.0 15.1 0.4": ["ecoterrorist"], "-1.3 7.3 6.0": ["arthroscopically"], "6.8 8.6 15.1": ["wees"], "8.9 19.5 6.3": ["ambidexterity"], "3.7 16.1 5.9": ["everythinged"], "-7.9 7.5 8.8": ["fibular"], "13.1 3.3 7.0": ["vibraphones"], "14.5 13.1 10.5": ["slanging"], "5.7 2.8 39.5": ["lakewide"], "3.8 8.1 3.7": ["rolofylline"], "9.4 7.4 7.6": ["coachload"], "4.5 5.4 19.4": ["infuser"], "13.4 8.3 7.1": ["majordomo"], "-2.8 4.6 1.2": ["pastorship"], "15.4 26.6 10.2": ["dismembers"], "17.1 16.8 11.7": ["noogies"], "2.5 10.6 4.5": ["plurinational"], "11.8 5.9 22.7": ["elevenses"], "7.4 3.0 12.3": ["airfreighted"], "-1.0 7.6 19.1": ["redbankgreen"], "8.0 6.7 1.0": ["unlikey"], "2.9 1.1 10.6": ["surplused"], "0.7 14.1 16.3": ["niyo"], "-0.2 2.1 6.9": ["famciclovir"], "11.7 18.2 4.8": ["pedantically"], "9.6 17.1 1.1": ["secuirty"], "-1.3 9.0 2.8": ["captopril"], "16.9 1.3 22.1": ["kited"], "5.2 0.1 -2.6": ["hryvnas"], "2.5 20.5 7.4": ["hyphenating"], "2.8 5.3 16.6": ["vigneron"], "9.7 5.1 8.9": ["ator"], "5.8 3.4 8.9": ["burnered"], "11.4 -2.8 3.6": ["impromtu"], "5.0 2.8 29.3": ["carambola"], "17.4 7.7 12.8": ["horded"], "24.8 13.9 27.1": ["rakers"], "-4.7 2.1 4.8": ["pionts"], "11.7 14.8 3.5": ["outmuscles"], "-1.6 4.6 9.8": ["flagfall"], "9.0 8.3 4.8": ["upscales"], "5.1 19.5 6.0": ["nonsence"], "7.2 15.7 -1.5": ["evangelizers"], "1.4 4.3 18.4": ["tia"], "8.0 9.8 5.6": ["sweeped"], "15.3 9.6 31.9": ["dainties"], "0.5 28.2 7.6": ["inocent"], "1.4 4.3 2.0": ["geoprocessing"], "-6.1 13.9 3.2": ["acknowlege"], "3.6 -1.4 0.7": ["puntos"], "12.6 11.7 19.6": ["crosshatch"], "7.2 15.6 -4.0": ["counry"], "4.8 1.4 16.4": ["voi"], "20.4 9.6 14.3": ["ultracool"], "10.8 6.1 29.9": ["coneys"], "6.0 3.6 6.9": ["langue"], "2.1 8.9 4.5": ["fini"], "1.9 11.0 13.4": ["nanomagnets"], "11.6 15.2 7.0": ["bandwagoners"], "-9.9 0.0 4.4": ["enplaned"], "9.6 24.1 16.4": ["coddlers"], "4.8 5.7 8.8": ["baghouses"], "1.1 10.6 35.8": ["anadromous"], "13.7 2.8 16.6": ["aggie"], "-0.2 6.3 2.0": ["nagarpalika"], "4.0 17.9 -2.1": ["recallable"], "13.2 9.6 14.3": ["puniest"], "1.7 8.1 29.4": ["haleem"], "8.5 -0.2 12.0": ["hein"], "20.6 15.5 15.1": ["cumulonimbus"], "2.0 7.1 5.6": ["kvetched"], "7.2 5.6 1.7": ["libary"], "15.2 11.0 29.1": ["nubbin"], "4.2 11.9 4.5": ["knols"], "4.1 15.4 1.2": ["hardhitting"], "-8.0 -0.3 5.1": ["hads"], "7.7 2.8 -1.0": ["departees"], "6.4 7.8 15.6": ["oya"], "8.4 -7.2 7.1": ["liposuctions"], "0.8 6.5 10.4": ["chromaticism"], "-6.6 13.5 -1.3": ["reciter"], "9.0 14.3 8.4": ["crosschecks"], "11.2 14.7 8.8": ["pauperized"], "14.6 4.1 11.7": ["declasse"], "-9.1 18.9 10.0": ["basestealing"], "7.1 19.2 5.7": ["nutbar"], "28.3 3.8 9.9": ["hoovers"], "4.4 0.9 -3.5": ["syas"], "9.0 9.0 3.2": ["wom"], "-3.1 -3.8 -0.2": ["multihousing"], "15.4 5.6 19.1": ["fishbone"], "-4.5 -2.2 -0.4": ["vitreoretinal"], "9.2 37.6 6.8": ["barbarianism"], "-1.8 18.7 19.0": ["hustlin"], "5.1 19.0 2.3": ["corruptness"], "11.9 17.2 3.1": ["bullheadedness"], "11.7 5.0 11.1": ["heatshield"], "7.1 5.8 7.3": ["uracil"], "16.1 4.5 11.3": ["slideout"], "2.3 2.7 11.6": ["hons"], "3.7 16.1 10.0": ["metafiction"], "0.3 22.0 12.3": ["miseducated"], "21.4 10.5 9.1": ["wiseacres"], "2.3 2.3 -0.4": ["msgs"], "-2.7 14.6 8.8": ["miscarries"], "2.4 4.7 4.1": ["particulalry"], "19.9 2.2 11.6": ["hypermarts"], "-5.4 10.1 5.9": ["psephologist"], "4.9 10.8 9.1": ["aneurisms"], "13.8 7.9 28.3": ["pemmican"], "-6.0 1.4 3.9": ["cervixes"], "6.5 13.7 -0.5": ["neuroprotectant"], "4.1 25.3 3.1": ["brethern"], "12.8 10.1 13.5": ["windcheater"], "2.7 10.8 5.0": ["adduction"], "14.1 6.6 12.0": ["stoep"], "5.9 12.5 7.9": ["axially"], "3.5 10.8 6.6": ["oportunities"], "-4.3 5.5 6.6": ["subvarsity"], "14.2 19.3 13.6": ["jaybird"], "25.6 19.7 27.2": ["superfish"], "7.8 3.3 9.0": ["pron"], "2.9 11.3 2.8": ["shtetls"], "17.8 12.3 14.1": ["brrr"], "-2.7 7.7 8.4": ["periodontists"], "6.7 12.2 19.6": ["intertank"], "0.8 6.5 10.9": ["lena"], "2.1 5.6 10.6": ["recordkeepers"], "14.2 16.3 15.7": ["undersurface"], "3.5 3.3 -0.2": ["mananger"], "-0.2 -1.4 18.4": ["russ"], "11.4 -3.4 21.8": ["lumpier"], "-7.1 5.8 3.4": ["hurst"], "9.5 0.0 6.7": ["extraordinare"], "8.6 11.7 13.1": ["collisional"], "7.5 16.0 34.9": ["rockpiles"], "14.2 16.9 22.5": ["outcompeting"], "4.6 5.8 13.0": ["callas"], "7.5 8.9 1.5": ["mobisode"], "0.6 9.8 15.1": ["dishearteningly"], "16.1 9.5 13.6": ["windmilled"], "10.4 11.8 1.9": ["superclass"], "-6.8 9.7 -1.1": ["detenue"], "-4.2 12.8 -1.0": ["abusable"], "2.8 21.7 14.7": ["blogrolls"], "8.9 13.0 10.7": ["shushes"], "5.1 -2.2 17.2": ["greenwaste"], "7.2 17.7 3.0": ["unfamilar"], "9.3 6.0 4.2": ["ambitous"], "21.8 3.6 25.3": ["encrusting"], "7.5 6.1 9.8": ["stockcars"], "9.7 10.7 13.1": ["soggiest"], "22.1 2.6 2.8": ["underperfoming"], "13.0 2.7 16.3": ["bocci"], "6.2 18.8 17.5": ["spirochete"], "4.6 12.6 5.8": ["fenceless"], "20.0 1.7 19.1": ["megaload"], "3.8 7.0 14.2": ["resegregating"], "-0.0 3.3 9.4": ["seve"], "6.3 15.8 0.1": ["surveillence"], "9.9 26.0 2.1": ["blindspots"], "4.9 10.2 9.8": ["bina"], "5.4 0.8 10.6": ["stopwork"], "4.6 11.6 0.8": ["systematised"], "-7.6 7.0 -0.7": ["kernicterus"], "21.3 2.3 6.8": ["superthin"], "19.5 1.0 14.7": ["leopardskin"], "5.1 14.4 14.6": ["owie"], "0.9 12.8 3.0": ["unappealable"], "19.3 12.9 13.1": ["stye"], "12.3 5.8 16.5": ["monokini"], "7.2 15.7 33.1": ["leadcore"], "8.1 15.0 17.8": ["monotones"], "-0.6 18.5 4.1": ["heterosexually"], "3.8 0.3 6.2": ["soundcards"], "8.9 14.1 15.4": ["ranga"], "1.7 22.9 1.9": ["peacefull"], "-6.4 3.9 6.9": ["interpassing"], "5.3 7.8 8.8": ["washermen"], "7.1 7.7 2.0": ["theranostic"], "7.6 5.0 18.3": ["slickline"], "13.6 19.5 5.2": ["deregulator"], "7.0 0.5 11.1": ["debbie"], "13.9 4.0 9.9": ["wildchild"], "9.3 14.1 17.4": ["participles"], "0.7 6.3 9.8": ["ely"], "6.2 14.2 12.5": ["jeepers"], "18.1 13.7 5.7": ["emblazed"], "-4.6 8.3 8.0": ["axilla"], "9.3 13.4 1.8": ["bootloaders"], "13.8 19.0 15.4": ["bucko"], "10.4 3.4 15.0": ["extravagent"], "9.1 4.4 22.0": ["daintier"], "-1.9 15.1 -1.9": ["comitting"], "0.1 5.6 1.9": ["epsiode"], "11.2 -5.9 21.5": ["serveware"], "21.3 2.1 12.8": ["scoopful"], "5.0 8.7 13.3": ["ankara"], "-1.7 2.6 6.8": ["rustication"], "20.0 11.2 10.1": ["clacks"], "5.2 16.8 12.4": ["eerier"], "14.5 18.1 10.0": ["apocalypses"], "0.0 -6.9 5.1": ["ington"], "10.0 4.5 1.7": ["backends"], "9.8 3.9 31.6": ["pommes"], "18.5 4.1 15.5": ["koozie"], "1.3 5.8 4.0": ["suis"], "13.5 5.5 34.6": ["beancurd"], "14.5 15.7 24.5": ["gemsbok"], "1.7 3.9 -0.0": ["suspicionless"], "4.7 13.0 12.1": ["lolz"], "-2.2 11.6 3.2": ["governate"], "11.3 1.2 11.4": ["iou"], "13.9 14.1 24.5": ["vlei"], "0.9 9.5 23.9": ["footrot"], "17.9 12.2 10.3": ["glossiest"], "2.0 3.9 18.6": ["hominess"], "7.1 8.7 22.3": ["feni"], "2.7 22.5 4.1": ["pathing"], "-2.9 9.2 9.9": ["unsually"], "-0.1 7.3 21.2": ["whenua"], "7.7 -5.8 0.0": ["rte"], "10.1 -4.6 14.0": ["coiffeur"], "14.9 -1.8 3.7": ["newsagencies"], "1.3 4.2 3.5": ["beneficiate"], "4.8 18.4 13.2": ["wrongheadedness"], "5.6 -1.0 15.7": ["shoplot"], "0.2 2.7 8.0": ["zalutumumab"], "13.2 10.6 10.3": ["skuzzy"], "8.7 11.3 9.7": ["jorts"], "13.3 4.1 3.8": ["pharmaco"], "5.1 25.1 4.1": ["profaning"], "5.7 20.6 13.3": ["unsympathetically"], "-1.5 22.2 2.0": ["percieve"], "9.3 14.5 10.9": ["semblances"], "10.5 13.0 20.6": ["washy"], "12.3 6.9 20.4": ["nipa"], "9.1 9.8 27.7": ["sessile"], "18.0 11.7 18.9": ["jibbing"], "19.1 22.6 19.1": ["magus"], "10.7 5.7 16.9": ["estancia"], "8.2 5.3 40.0": ["mofongo"], "7.4 14.9 2.7": ["implosive"], "7.9 16.6 -0.4": ["inuring"], "-3.5 -1.2 9.4": ["scm"], "15.1 12.8 9.7": ["refashions"], "4.9 18.5 14.9": ["supertyphoon"], "3.3 14.4 8.3": ["tractive"], "12.4 2.4 15.4": ["powdercoated"], "4.0 -4.7 18.4": ["tackies"], "10.9 -1.8 9.3": ["rotogravure"], "4.7 -1.8 5.7": ["tounament"], "12.0 24.1 11.5": ["assumptive"], "-4.1 3.3 13.1": ["trimethoprim"], "3.0 20.6 5.0": ["advertently"], "-3.0 7.9 2.4": ["contextualising"], "-0.1 19.3 7.2": ["pepole"], "5.3 19.2 9.3": ["tumorous"], "-1.2 7.8 4.7": ["wheter"], "21.0 13.4 14.8": ["splendorous"], "8.7 10.8 10.8": ["antilock"], "2.1 7.5 9.9": ["econmic", "autobox"], "12.5 7.8 17.0": ["pomo"], "2.7 7.8 16.8": ["sona"], "19.7 16.4 10.2": ["kablooey"], "-4.3 11.3 11.9": ["godsons"], "5.4 5.1 16.1": ["malamutes"], "-1.3 12.0 4.4": ["chameleonlike"], "2.6 -7.9 9.9": ["marion"], "2.0 12.5 7.6": ["obsequies"], "6.6 2.9 17.1": ["steez"], "11.3 14.4 25.5": ["kalanchoe"], "4.8 2.9 0.4": ["anent"], "-6.8 6.4 8.8": ["longsnapper"], "-2.3 13.0 9.9": ["overexert"], "18.8 17.6 12.6": ["rocketships"], "-1.0 5.4 6.1": ["songful", "nitecap"], "10.5 23.5 1.9": ["nauseate"], "4.2 15.4 4.4": ["parapsychologist"], "-10.9 10.9 5.0": ["pimozide"], "9.4 9.2 6.4": ["sprayable"], "-5.3 25.6 3.6": ["positionings"], "7.4 6.4 9.6": ["keyers"], "2.1 18.0 2.5": ["loyals"], "3.6 8.6 13.9": ["thatcher"], "5.6 10.2 -0.5": ["programmme"], "-5.1 14.9 4.6": ["kashmiri"], "1.8 22.2 2.8": ["ontologically"], "-0.3 17.1 14.1": ["jadedness"], "-3.1 3.6 12.2": ["checkstop"], "13.5 23.9 3.5": ["volk"], "2.7 5.9 11.9": ["strick"], "19.7 14.7 20.0": ["wolfhound"], "4.9 12.4 9.6": ["isto"], "16.1 16.5 10.8": ["drek"], "3.2 6.5 4.1": ["wasnot"], "4.4 2.9 31.8": ["palak"], "4.8 10.5 11.7": ["goalside"], "4.2 14.7 17.4": ["catched"], "5.1 18.9 20.7": ["nester"], "4.7 -14.2 9.9": ["ium"], "1.4 12.3 5.4": ["circumscribes"], "1.7 6.5 19.0": ["cocktailing"], "8.8 24.4 3.9": ["guileful"], "2.9 7.1 9.7": ["subadvisers"], "2.8 1.1 8.8": ["apl"], "22.7 19.2 8.5": ["everwhere"], "0.9 7.7 11.0": ["hz"], "6.7 8.4 9.9": ["culty"], "-2.1 10.5 11.4": ["asymptotic"], "0.6 23.2 8.8": ["regnant"], "0.3 3.6 9.2": ["chand"], "9.8 10.7 10.7": ["contractualization"], "4.5 4.1 13.3": ["minuto"], "8.1 3.2 5.8": ["semiskilled"], "7.3 0.5 2.3": ["telecenters"], "11.4 8.2 7.3": ["switzerland"], "8.1 12.8 13.1": ["craton"], "6.4 13.3 12.5": ["retrosexual"], "-2.8 13.3 4.1": ["dargahs"], "4.4 13.5 11.9": ["cretinism"], "4.4 17.2 9.3": ["unreliably"], "5.9 10.2 10.1": ["trippingly"], "11.0 12.5 0.5": ["theright"], "10.4 12.2 14.9": ["unfussed"], "-2.3 -0.4 3.8": ["underwears"], "3.8 2.1 16.7": ["packhouses"], "10.6 13.3 12.6": ["irresistibility"], "11.8 5.8 17.3": ["wif"], "18.7 3.8 18.4": ["gateposts"], "-5.1 19.3 -4.0": ["discipled"], "0.8 11.5 8.9": ["immunogens"], "10.7 21.0 8.0": ["fearmonger"], "14.0 11.3 -0.6": ["kickbucks"], "9.7 13.7 15.3": ["sliothar"], "5.6 23.2 6.9": ["gossiper"], "5.1 1.7 10.4": ["arn"], "11.3 18.6 8.0": ["strangleholds"], "8.7 4.6 6.2": ["quintuplet"], "-0.1 0.2 -2.6": ["extentions", "articleship"], "12.1 6.0 6.6": ["frente"], "-0.5 10.7 6.2": ["hypomanic"], "4.5 10.7 11.9": ["tallness"], "-1.4 16.2 7.3": ["upline"], "1.7 13.5 8.1": ["hortatory"], "-0.9 7.0 7.9": ["moisturization"], "7.5 9.7 15.4": ["chappal"], "0.6 14.6 12.3": ["endophytes"], "0.8 10.1 4.0": ["robinho"], "8.3 4.7 12.1": ["blufftop"], "-1.5 0.5 13.4": ["haltered"], "-5.6 0.2 -0.9": ["legis"], "0.1 -2.7 0.9": ["peh"], "-4.8 1.3 -6.4": ["redesignating"], "2.4 10.3 0.2": ["interlinkages"], "5.0 23.3 12.3": ["playerbase"], "17.3 5.9 15.8": ["buzzcut"], "11.7 8.7 9.8": ["ais"], "13.0 33.3 11.6": ["flatterer"], "8.6 11.0 3.3": ["webapps"], "8.7 2.0 30.6": ["muffaletta"], "5.0 9.2 7.7": ["carbonyl"], "6.2 1.3 1.9": ["iniparib"], "6.0 10.8 29.8": ["caddisflies"], "-3.7 5.6 12.6": ["rurality"], "3.4 4.2 4.0": ["exparte"], "5.6 3.7 2.4": ["lur"], "-1.7 12.0 1.2": ["critizing"], "5.6 25.3 4.3": ["batallions"], "-1.7 7.8 22.0": ["ecoregions"], "5.3 16.2 6.1": ["overhits"], "9.8 13.9 12.7": ["lambent"], "1.7 -3.1 -0.5": ["neurodiagnostic"], "4.9 -2.4 6.1": ["senza"], "5.2 27.5 17.2": ["nevers"], "9.8 17.0 1.4": ["chancelleries"], "11.0 1.7 18.9": ["crewel"], "15.6 22.9 8.0": ["amputates"], "12.2 7.2 7.2": ["tricolore"], "8.7 12.5 9.0": ["phenylethylamine"], "3.4 -1.2 4.4": ["tooks"], "2.1 13.9 15.5": ["altimetry"], "0.7 12.2 9.0": ["mastership"], "10.3 5.3 3.4": ["tided"], "2.7 15.7 11.3": ["couldve"], "5.1 11.8 15.6": ["omentum"], "23.4 4.8 4.9": ["renationalize"], "16.6 8.3 24.5": ["bilby"], "2.3 4.4 16.6": ["deaccessioning"], "-8.6 17.6 -0.5": ["jurisprudent"], "1.9 1.9 2.8": ["seaons"], "4.5 14.6 -0.5": ["proove"], "4.0 -0.0 16.2": ["calcined"], "-3.8 7.8 7.6": ["numberous"], "-9.6 4.2 0.3": ["psychostimulants"], "5.7 8.5 9.2": ["afterglows"], "8.6 17.2 10.5": ["postpartisan"], "-0.5 -2.5 11.1": ["tweenage"], "16.9 4.8 28.8": ["yumminess"], "4.1 4.4 4.6": ["reroofed"], "4.1 -1.8 9.0": ["minimarket"], "15.9 4.7 35.5": ["tureens"], "1.7 4.1 14.6": ["multicrystalline"], "0.5 3.0 10.4": ["macher"], "6.6 2.7 3.3": ["plantwide"], "10.5 3.2 9.8": ["quartier"], "5.5 2.7 8.5": ["hightops"], "20.6 8.3 15.4": ["miaow"], "8.5 27.6 9.1": ["manouevres"], "2.6 10.0 4.9": ["inorganics"], "9.8 8.8 36.2": ["debone"], "5.9 18.5 13.1": ["everlastingly"], "-3.1 16.4 4.0": ["counterexamples"], "3.3 24.4 7.2": ["minimalize"], "-2.0 1.7 6.2": ["nonpregnant"], "20.7 10.2 8.0": ["moused"], "-7.5 11.3 2.2": ["connectiveness"], "16.1 5.8 21.4": ["scrotums"], "9.7 -0.9 25.6": ["comida"], "6.3 20.3 0.7": ["founts"], "6.1 -2.2 2.1": ["usership"], "-3.0 3.1 -0.1": ["diabetologist"], "-0.5 7.7 4.0": ["idebenone"], "9.1 17.1 13.8": ["substrata", "disap"], "3.8 13.2 15.2": ["heartfacee"], "6.8 9.5 7.9": ["overline"], "7.3 6.0 5.8": ["understeered"], "3.1 7.1 8.2": ["obligatorily"], "10.6 12.0 23.0": ["dispersers"], "5.9 9.7 7.9": ["ferromagnetism"], "17.4 27.7 16.9": ["lycanthrope"], "6.0 4.9 14.0": ["woon"], "-3.2 3.1 2.6": ["poin"], "14.3 23.0 -2.9": ["reconquering"], "-3.3 15.0 6.6": ["thik"], "-0.8 -1.7 11.4": ["perforatum"], "27.8 8.6 26.4": ["tikis"], "-7.3 14.5 -0.2": ["appologize"], "16.0 9.2 19.6": ["censer"], "6.7 5.7 8.6": ["nonfans"], "-0.2 5.4 15.9": ["arre"], "10.1 9.3 17.6": ["tierra"], "9.0 12.5 34.9": ["backstrap"], "10.9 18.6 6.6": ["toxically"], "-3.4 -4.8 0.5": ["implantology"], "-8.4 10.6 7.2": ["fibo"], "-6.0 -0.4 0.2": ["basektball"], "-2.0 -2.5 -3.8": ["tial"], "-1.1 5.3 1.1": ["carburettors"], "3.8 0.5 15.6": ["agronomics"], "18.8 20.2 15.6": ["warpaint"], "4.6 17.0 6.8": ["slyest"], "2.9 1.9 10.1": ["pcm"], "3.1 14.2 10.6": ["beti"], "6.8 5.0 11.1": ["nonreturnable"], "5.6 7.0 14.6": ["ork"], "-10.5 2.4 5.0": ["reoffense"], "4.8 6.0 9.8": ["narrowings"], "-4.4 20.1 -0.2": ["databus"], "1.5 3.2 15.6": ["lungis"], "-0.2 -6.3 8.4": ["econveyance"], "18.6 2.2 31.3": ["rusk"], "17.2 18.5 19.3": ["leylandii"], "4.3 18.2 12.1": ["hypermiler"], "11.3 4.0 19.5": ["complexioned"], "8.7 3.4 12.0": ["princessy"], "3.6 12.4 4.3": ["orthotopic"], "3.3 6.5 1.5": ["tiem"], "9.9 17.9 15.0": ["dowser"], "-2.4 -3.8 8.8": ["sportif"], "-3.2 9.2 -0.1": ["theyhave"], "1.7 13.3 11.8": ["vascularized"], "13.6 19.4 15.2": ["motherfuckin"], "19.2 8.8 19.0": ["teeniest"], "11.7 10.1 13.2": ["kneeboard"], "-4.4 6.4 1.1": ["renumber"], "1.2 -12.4 6.4": ["prelimary"], "8.0 3.4 25.8": ["snacky"], "8.0 -2.1 10.6": ["polyether"], "-2.7 11.1 7.9": ["neuroanatomical"], "0.3 1.4 1.1": ["apremilast"], "20.8 9.7 20.5": ["biospheres"], "1.2 6.0 -2.8": ["potentiated"], "5.6 13.0 7.8": ["iphonia"], "1.4 12.7 9.3": ["articulator"], "9.3 18.5 12.2": ["anythings"], "3.6 16.0 7.6": ["impoliteness"], "6.1 5.9 27.3": ["bobolink"], "0.0 8.8 15.6": ["enoteca"], "-9.3 5.0 2.5": ["extubation"], "6.0 6.4 6.7": ["reservationists"], "3.9 5.7 12.4": ["flowability"], "9.7 3.7 4.8": ["hungama"], "13.6 1.1 16.9": ["presalt"], "4.8 1.5 6.5": ["minitour"], "4.1 23.1 6.1": ["traducers"], "4.7 1.2 4.7": ["remerchandising"], "3.2 1.3 6.1": ["chromogenic"], "19.0 10.8 7.7": ["skylit"], "1.4 18.9 11.8": ["stoppin"], "12.5 15.1 6.8": ["spycam"], "-5.0 10.8 6.7": ["mediastinoscopy"], "5.0 9.7 20.7": ["mitered"], "10.0 16.2 8.8": ["proably"], "3.4 7.4 4.0": ["prevalance"], "8.5 -10.6 12.5": ["vaca"], "0.0 13.5 11.3": ["intratumoral"], "6.8 18.1 7.5": ["bleeper"], "18.3 1.5 -3.2": ["programer"], "8.4 2.2 10.3": ["chicly"], "6.8 3.5 11.8": ["dabbawallahs"], "4.5 1.0 -4.6": ["isalso"], "7.0 17.8 14.3": ["pid"], "-2.4 4.3 1.0": ["misconnected"], "6.3 12.3 17.0": ["organismic"], "6.4 8.0 8.4": ["mand"], "3.1 6.7 5.6": ["interlaces"], "1.0 14.3 3.1": ["overfunding"], "2.7 23.7 5.6": ["sanyasi"], "-0.4 0.4 9.8": ["glycopyrrolate"], "7.5 15.0 20.7": ["sporozoites"], "2.2 19.4 8.7": ["airdrome"], "6.4 -3.0 6.5": ["hairbands"], "11.0 15.3 17.7": ["yobbo"], "0.7 6.5 3.2": ["quilty"], "4.8 10.5 10.3": ["colorfast"], "0.3 0.6 11.2": ["juste"], "11.8 12.1 12.3": ["unrideable"], "2.5 5.4 4.8": ["fileserver"], "-7.2 8.9 10.3": ["checkstops"], "15.8 12.9 28.0": ["everglades"], "-6.1 7.9 -3.7": ["reclusion"], "7.8 19.3 19.5": ["pesty"], "8.3 9.1 33.3": ["pintxos"], "-1.9 -0.6 1.0": ["telestroke"], "18.1 9.4 16.0": ["egad"], "3.1 10.3 21.0": ["subsp"], "9.0 20.9 4.1": ["fsck"], "6.8 14.1 13.1": ["overfamiliar"], "15.8 18.3 25.4": ["draggin"], "3.2 7.0 6.4": ["maharashtra"], "11.6 11.0 13.1": ["regasified"], "1.7 5.6 14.5": ["mahangu"], "5.7 1.0 20.1": ["incude"], "6.4 16.1 12.6": ["biatch"], "-2.6 -0.6 2.4": ["addres"], "18.7 5.0 45.1": ["shitake"], "18.7 12.0 8.2": ["megajoule"], "12.1 17.6 11.8": ["colonially"], "-1.3 4.5 16.5": ["gawin"], "1.0 12.5 15.3": ["sth"], "7.1 11.3 -5.9": ["effeciency"], "3.7 20.6 6.7": ["shoah"], "7.9 8.2 6.6": ["mlns"], "2.0 13.5 3.3": ["skillfull"], "-2.0 18.1 4.6": ["proximities"], "7.2 15.4 13.6": ["nanoprobes"], "2.5 7.1 12.9": ["liberalizations"], "19.1 18.6 20.4": ["heinie"], "-3.2 14.7 9.8": ["filicide"], "15.8 13.0 4.8": ["genuflects"], "4.0 12.1 4.5": ["imitable"], "10.6 -4.8 4.5": ["bauma"], "12.7 16.2 16.7": ["omo"], "-5.1 11.2 7.3": ["asportation"], "10.1 23.3 18.7": ["sandbagger"], "14.3 10.3 45.8": ["smallie"], "4.7 9.4 14.9": ["puta"], "-3.7 2.0 -3.7": ["higherups"], "1.3 20.6 6.6": ["feelingly"], "-3.1 -0.0 2.2": ["elminated"], "-1.0 1.7 5.5": ["comanager"], "3.5 17.1 -0.1": ["storys"], "12.3 14.5 10.9": ["devolutionary"], "1.8 7.3 8.7": ["pentathletes"], "1.6 -2.1 3.7": ["centum"], "5.0 13.3 14.9": ["hiya"], "12.9 2.2 7.7": ["advisery"], "17.8 -1.0 8.0": ["biogasoline"], "7.0 7.3 -3.5": ["federates"], "8.5 5.8 16.4": ["calypsos"], "6.7 7.6 8.6": ["angelina"], "18.4 27.2 12.0": ["nemisis"], "-3.1 2.4 5.0": ["vani"], "2.9 6.0 7.2": ["thermosets"], "6.5 13.4 11.3": ["chromatically"], "4.1 3.5 11.7": ["bures"], "3.6 27.4 13.1": ["wilier"], "-3.7 4.3 9.8": ["hypophosphatemia"], "-0.8 28.3 9.7": ["liege"], "-1.7 2.0 6.2": ["transaminases"], "0.6 17.7 8.1": ["goondaism"], "4.8 22.7 7.3": ["opportunely"], "-5.3 13.9 8.2": ["neorealism"], "4.0 11.5 8.1": ["dickey"], "-0.7 11.9 9.1": ["nonuniformed"], "5.1 1.3 10.3": ["pul"], "6.3 2.9 7.4": ["stablized"], "13.1 15.7 16.5": ["refractions"], "-3.6 8.2 10.5": ["kinetochore"], "14.5 17.2 18.3": ["suckas"], "5.6 20.0 12.4": ["windshift"], "16.4 10.5 13.2": ["megalopolises"], "4.4 10.5 10.8": ["pyroxene"], "19.2 1.6 17.0": ["handcarved"], "1.3 0.3 22.3": ["instream"], "-1.4 17.0 11.1": ["paisanos"], "7.0 1.6 10.1": ["crosslink"], "3.9 8.3 13.8": ["tcp"], "6.1 0.9 3.3": ["freefloat"], "5.8 6.0 16.3": ["wors"], "11.5 10.8 23.8": ["gaillardia"], "-5.6 8.2 0.7": ["underutilize"], "1.4 22.0 1.9": ["dehumanises"], "13.9 -2.0 6.8": ["ahm"], "5.7 6.6 11.0": ["uae"], "7.4 21.6 22.9": ["lacewings"], "0.5 2.4 6.6": ["catechisms"], "11.6 4.0 20.7": ["cheez"], "8.8 13.2 6.7": ["glamourise"], "4.5 6.3 7.2": ["notarizations"], "3.3 1.3 43.1": ["yellowfins"], "18.7 6.4 10.2": ["metalworks"], "15.5 12.2 33.7": ["dishpan"], "21.1 18.9 15.4": ["meatspace"], "-3.1 4.5 4.3": ["optionors"], "3.1 -0.9 19.4": ["limnology"], "4.3 8.1 22.8": ["kokako"], "1.9 11.6 2.9": ["acccused"], "17.1 3.9 13.9": ["loa"], "19.8 11.8 7.4": ["dimentional"], "3.6 14.4 6.6": ["freemason"], "15.6 6.6 6.7": ["premerger"], "2.7 18.0 12.3": ["wab"], "-0.0 8.1 -1.2": ["onone"], "-1.3 14.8 12.7": ["manhwa"], "-5.5 4.8 -6.6": ["acceptation"], "2.9 16.5 3.4": ["impetuses"], "5.0 13.9 5.8": ["dryline"], "1.9 6.3 6.5": ["freedman"], "20.2 16.7 20.2": ["portcullis"], "16.5 8.2 17.1": ["scally"], "17.4 11.3 9.4": ["handwarmers"], "8.0 6.7 14.3": ["ovalbumin"], "14.6 4.3 11.1": ["companied"], "-6.0 14.4 11.7": ["surprized"], "-6.2 6.3 5.7": ["includable"], "3.2 5.4 16.7": ["tankinis"], "13.1 1.5 3.6": ["preceeds"], "10.2 13.9 10.3": ["cowled"], "3.8 -4.5 4.4": ["coproductions"], "5.1 7.8 7.2": ["aciclovir"], "13.3 -5.0 20.0": ["milkpowder"], "8.5 4.4 10.4": ["dehorned"], "10.1 15.0 13.2": ["denature"], "16.3 18.9 19.3": ["dodecahedron"], "-7.1 9.5 9.3": ["subthreshold"], "6.0 11.1 18.1": ["lugnuts"], "6.7 4.2 4.2": ["decontrolling"], "-2.7 11.1 5.4": ["recomposition"], "15.4 4.2 16.2": ["giftwrap"], "16.8 14.6 1.9": ["trodding"], "1.3 17.7 -1.8": ["critism"], "7.7 2.4 7.5": ["classifed"], "-1.5 0.3 20.8": ["metroparks"], "15.8 12.2 12.1": ["shylock"], "6.0 17.3 8.1": ["yobbery"], "12.1 -1.1 18.9": ["rill"], "1.1 19.0 16.5": ["barkeeper"], "13.0 18.1 32.3": ["whooper"], "2.2 18.7 6.2": ["tactlessness"], "-3.8 6.8 3.3": ["declinations"], "12.1 7.6 26.0": ["cupfuls"], "9.4 -2.1 12.6": ["terrane"], "10.0 3.0 13.4": ["walkie"], "18.7 10.3 20.3": ["lidless"], "7.7 2.2 12.3": ["brooke"], "-1.8 4.2 15.5": ["kasing"], "9.8 16.2 20.1": ["homophones"], "4.9 2.5 4.2": ["braze"], "6.7 8.0 9.0": ["induration"], "-6.8 9.5 5.7": ["acetylated"], "20.2 13.3 9.3": ["swallowers"], "15.3 1.9 15.9": ["galleried"], "9.0 27.7 9.7": ["shiite"], "4.9 10.2 3.2": ["gropings"], "-1.9 3.6 9.8": ["bromfenac"], "5.3 12.9 3.6": ["expence"], "1.5 4.0 6.6": ["punkier"], "10.1 6.5 3.6": ["guestbooks"], "14.1 9.6 18.6": ["chandler"], "5.4 14.9 2.4": ["tyrannically"], "1.0 14.2 13.1": ["sitcommy"], "-0.1 7.7 19.3": ["pwedeng"], "3.2 10.1 -3.0": ["hatte"], "11.8 8.1 14.2": ["shinpads"], "6.6 13.1 9.0": ["grrl"], "20.7 4.9 5.0": ["bossnappings"], "4.0 1.2 8.7": ["casthouse"], "9.2 3.5 20.6": ["manses"], "10.3 15.3 17.5": ["getcha"], "1.2 11.2 1.1": ["documentarist"], "7.1 14.8 6.2": ["standoffishness"], "-1.2 12.5 10.0": ["blastomeres"], "6.5 16.1 18.5": ["oni"], "-1.6 17.7 9.8": ["anaplastic"], "17.6 14.0 26.0": ["jackdaw"], "22.5 6.6 10.1": ["piddled"], "7.2 8.1 2.5": ["initialisation"], "7.3 10.6 14.9": ["overtaxation", "jacko"], "6.1 6.9 8.3": ["previsions"], "12.0 -1.4 10.0": ["bunging"], "-3.2 5.2 4.5": ["thte"], "18.2 2.4 14.0": ["organdy"], "2.5 17.6 8.2": ["lessness"], "17.4 14.9 23.9": ["hod"], "-2.2 6.0 19.8": ["fucoidan"], "8.0 8.3 10.8": ["speedballs"], "15.3 7.8 11.9": ["micrograph"], "8.6 9.8 9.4": ["julia"], "10.2 2.7 3.3": ["typographers"], "5.1 14.1 13.4": ["reinjures"], "-2.8 9.2 4.7": ["ius"], "-5.1 -4.6 -2.7": ["ory"], "10.0 8.2 4.6": ["acorss"], "5.0 11.1 13.8": ["sabi"], "8.5 18.2 22.7": ["mendicancy"], "18.9 24.3 33.5": ["mozzie"], "4.2 15.4 14.6": ["quatrain"], "8.1 9.7 9.6": ["adulterators"], "4.3 17.6 13.4": ["saveable"], "15.3 5.0 6.2": ["nogal"], "4.4 7.0 6.8": ["nhs"], "11.6 8.0 4.8": ["bharat"], "0.7 4.6 7.1": ["pueden"], "10.3 4.0 18.0": ["cholestrol"], "-7.7 9.1 22.8": ["droughty"], "-9.4 13.0 0.3": ["lections"], "3.7 -0.7 17.3": ["overcounted"], "20.9 7.0 16.4": ["kitchy"], "12.2 0.2 14.3": ["vente"], "-3.0 5.4 8.8": ["comparitive"], "5.4 3.7 10.5": ["hydroprocessing"], "1.6 0.6 9.6": ["timeshifted"], "1.6 7.3 9.3": ["badi"], "4.6 3.0 20.6": ["chasuble"], "3.3 13.2 -0.7": ["opnion"], "11.2 22.6 6.5": ["nutbag"], "3.5 11.0 3.2": ["asan"], "0.6 -0.3 8.7": ["folksier"], "1.4 -2.5 10.9": ["prorata"], "2.2 6.6 -0.7": ["intercalation"], "-3.8 12.2 5.5": ["deconditioned"], "5.1 9.5 9.4": ["catfighting"], "1.1 2.8 2.3": ["gove"], "9.2 12.0 15.0": ["doody"], "17.8 14.6 18.9": ["brushwood"], "19.7 -1.4 0.3": ["gaat", "providerof"], "11.9 7.0 12.8": ["mockney"], "4.4 9.1 -1.9": ["canvasing"], "0.4 5.8 6.6": ["fanciable"], "-1.2 5.8 17.1": ["pierre"], "-6.2 8.5 14.9": ["coeliacs"], "7.0 17.8 4.5": ["limn"], "13.0 9.9 5.7": ["unpretty"], "0.6 3.8 10.8": ["noncompeting"], "9.0 7.2 19.0": ["slappin"], "-2.5 5.2 10.4": ["hyperthyroid"], "3.4 10.7 2.6": ["froward"], "14.8 -1.5 15.2": ["peelable"], "4.8 2.2 9.6": ["damaka"], "20.6 1.6 15.0": ["daises"], "9.7 13.4 16.2": ["kinkiness"], "4.5 -2.9 -4.0": ["thefollowing"], "3.2 10.6 15.4": ["chara"], "18.3 10.5 13.1": ["tiltable"], "-0.1 3.5 4.6": ["cardioprotection"], "1.2 4.3 1.3": ["eal"], "5.0 7.4 16.2": ["snowblowing"], "11.1 4.7 16.2": ["dunt"], "-13.1 3.8 0.5": ["clarificatory"], "7.7 16.6 -0.5": ["enthrallment"], "11.2 -2.7 -1.5": ["rtgs"], "1.3 -3.8 -2.7": ["yeras"], "10.3 9.7 14.3": ["treasurys"], "2.5 12.4 9.6": ["vechicle"], "0.1 2.0 -7.1": ["documental"], "7.1 3.7 16.6": ["alexis"], "4.2 2.0 0.0": ["hase"], "9.2 9.2 5.6": ["facebooking"], "9.3 4.8 15.9": ["drivethrus"], "2.0 13.3 4.0": ["decampees"], "7.3 15.3 7.0": ["overspenders"], "6.7 -1.4 12.9": ["lowrise"], "2.1 8.8 8.7": ["insidery"], "7.7 12.8 16.6": ["noel"], "7.9 7.8 4.2": ["resampled"], "9.6 0.3 3.3": ["blo"], "3.2 10.3 6.9": ["fundholders"], "5.1 4.7 9.7": ["puwede"], "19.2 3.8 25.3": ["budgerigar"], "16.1 4.7 15.9": ["tilework"], "3.4 1.1 14.0": ["spx"], "0.8 0.5 8.8": ["quinquennial"], "9.6 6.3 22.5": ["frit"], "7.1 12.6 18.8": ["delaminated"], "7.4 0.6 23.6": ["merinos"], "14.3 15.2 13.0": ["recesssion"], "2.1 7.2 7.5": ["ecovillage"], "6.6 2.9 11.5": ["psu"], "7.2 17.4 30.9": ["sapwood"], "2.3 3.6 -5.7": ["ongoings"], "7.8 -2.8 6.9": ["sih"], "-1.8 9.5 3.4": ["desistance"], "-8.2 8.4 3.8": ["minyanim"], "-0.3 9.8 13.6": ["ganyan"], "-0.5 19.1 14.4": ["debarkation"], "18.6 15.9 16.3": ["pooing"], "8.5 4.8 8.1": ["develpment"], "8.9 17.3 4.0": ["coutnry"], "14.1 17.7 10.2": ["flabbiness"], "-3.8 2.3 5.9": ["interclick"], "11.3 16.6 3.5": ["indigenise"], "5.7 -6.1 -5.1": ["musique"], "-9.5 6.8 4.8": ["cotrimoxazole"], "-2.5 5.7 5.2": ["antiinflammatory"], "15.1 16.1 8.1": ["offerer"], "16.0 5.4 13.6": ["backblocks"], "3.2 2.4 11.7": ["trailway"], "-5.2 5.4 4.5": ["ssaid"], "-7.0 12.9 8.1": ["walkons"], "-1.0 3.1 12.0": ["hopefuly"], "-8.1 -2.9 -0.8": ["triptorelin"], "10.7 11.7 18.8": ["kolam"], "16.8 -1.6 13.5": ["hotplates"], "10.9 12.1 6.4": ["convulsively"], "8.2 11.0 10.1": ["tiptronic"], "0.6 -6.3 12.8": ["trenbolone"], "-1.6 1.4 4.9": ["voy"], "-0.4 3.4 2.5": ["transparancy"], "8.3 13.0 18.1": ["lifeboatmen"], "11.4 15.6 16.6": ["atcha"], "3.4 -3.7 5.4": ["passouts"], "7.3 20.1 14.8": ["lousiness"], "17.9 -8.7 10.0": ["bbw"], "25.6 12.3 26.9": ["cruller"], "16.5 9.6 11.4": ["onanism"], "8.8 7.4 15.5": ["slatternly"], "5.8 14.4 5.5": ["cesspits"], "5.7 7.9 11.0": ["lloyd"], "0.3 5.7 15.9": ["minsan"], "6.9 0.4 12.6": ["repointed"], "14.1 8.7 17.5": ["salchow"], "20.1 6.9 7.0": ["syle"], "1.3 4.0 8.6": ["flexiblity"], "0.7 16.2 5.0": ["kindheartedness"], "7.1 0.3 -5.0": ["personalises"], "20.5 8.7 15.9": ["treehugger"], "7.6 17.5 41.8": ["ringneck"], "2.1 -2.7 -5.0": ["performa"], "10.0 11.9 20.5": ["ashe"], "-2.0 15.8 7.9": ["oversubscribe"], "6.3 18.5 40.0": ["overfish"], "4.2 1.4 0.5": ["newser"], "11.3 2.2 0.1": ["asignificant"], "25.7 -3.4 8.3": ["offseting"], "0.4 12.1 3.1": ["hierarch"], "-6.9 14.7 -2.8": ["professedly"], "7.0 4.3 12.6": ["chainstay"], "6.4 4.2 28.7": ["kine"], "6.8 21.4 3.9": ["backsliders"], "5.5 7.3 7.9": ["smoothens"], "-1.5 8.4 10.7": ["diwaniya"], "6.1 15.2 5.6": ["innoculation"], "4.5 12.4 14.6": ["disarticulated"], "9.3 18.2 14.8": ["moonlet"], "9.4 6.8 1.9": ["prangs"], "16.5 3.0 29.1": ["waterlily"], "6.9 13.3 10.9": ["teebox"], "8.5 4.4 8.7": ["colourant"], "9.0 14.8 13.3": ["yeesh"], "1.3 7.7 9.5": ["hould"], "-5.7 1.6 8.2": ["eligibile"], "1.7 8.2 3.5": ["cytochrome"], "17.9 9.3 11.5": ["gazer"], "2.7 11.1 15.7": ["unbaptized"], "-1.0 10.6 3.7": ["realtionship"], "17.8 17.2 18.5": ["dewdrops"], "1.5 5.5 2.3": ["nonemployees"], "5.1 21.1 24.9": ["canids"], "6.4 11.1 15.2": ["mantri"], "21.2 9.9 3.1": ["lightyears"], "9.1 2.1 5.8": ["scenography"], "18.3 4.3 52.8": ["littlenecks"], "7.8 13.1 21.7": ["whitebark"], "-4.4 10.7 25.8": ["renourished"], "-3.0 6.0 8.9": ["daytimes"], "-3.7 8.0 9.0": ["tearfulness"], "0.2 6.5 0.5": ["adducing"], "8.1 2.7 13.5": ["twinset"], "9.1 12.7 25.7": ["halvah"], "9.3 6.7 4.8": ["phrasebooks"], "11.3 4.8 12.5": ["perth"], "0.9 6.5 1.2": ["revisioning"], "9.3 0.8 13.7": ["playscapes"], "9.3 10.3 7.9": ["skyjacker"], "2.0 11.6 5.8": ["midlines"], "0.2 -4.5 -1.1": ["diabetologists"], "7.1 -2.4 6.3": ["saxaphone"], "12.6 12.8 0.8": ["glamorises"], "-3.2 22.9 1.1": ["incarnational"], "-8.2 8.0 -3.3": ["dyspnoea"], "3.3 2.2 14.4": ["sola"], "27.3 16.6 12.9": ["frikkin"], "-6.2 4.0 9.0": ["normed"], "8.3 3.6 6.5": ["prin"], "11.7 10.9 16.1": ["cholo"], "7.4 20.3 -1.3": ["advocators"], "14.6 9.3 32.4": ["shoreward"], "7.1 17.6 9.9": ["traversable"], "16.3 -4.5 6.2": ["trendily"], "5.7 -4.7 6.4": ["trampolinist"], "15.7 9.3 23.3": ["coatimundi"], "14.5 25.5 17.5": ["zombification"], "10.3 4.7 5.6": ["demolishment"], "5.3 7.9 19.6": ["doublers"], "-5.3 11.5 12.2": ["remounts"], "4.0 6.3 12.3": ["skiied"], "-8.7 9.1 6.9": ["huey"], "-0.2 11.0 9.6": ["replicative"], "2.5 10.8 8.3": ["tidak"], "14.6 2.5 14.5": ["sqaure"], "-4.2 -4.3 8.8": ["hyperandrogenism"], "4.1 4.6 14.0": ["hsing"], "17.2 10.3 13.6": ["beefcakes"], "4.6 2.8 15.8": ["kuk"], "8.8 3.4 16.2": ["duk"], "2.8 18.7 9.4": ["declaratively"], "3.2 3.2 9.3": ["bahamas"], "3.5 27.0 5.5": ["guardpost"], "0.9 9.8 21.0": ["toxoplasma"], "10.0 -0.5 12.6": ["shapelier"], "5.2 6.8 8.8": ["glucan"], "8.6 12.8 34.0": ["phoebe"], "2.6 11.6 -3.5": ["underpar"], "-2.5 4.3 10.6": ["noninjury"], "20.2 2.3 19.1": ["bentwood"], "-3.2 11.1 1.4": ["multipartyism"], "8.4 4.0 17.4": ["edgings"], "14.5 20.2 11.9": ["joylessness"], "-4.9 4.3 26.8": ["herbage"], "12.0 -1.4 9.4": ["otra"], "6.2 7.4 8.9": ["bemedalled"], "-11.5 0.1 0.3": ["subspecialist"], "0.5 6.1 7.2": ["selenide"], "2.6 16.0 12.7": ["untaught"], "11.0 20.8 5.9": ["inflationists"], "25.4 5.0 25.4": ["cornhusks"], "5.2 7.0 8.3": ["consulations"], "15.0 0.5 19.1": ["baluster"], "10.8 4.8 6.4": ["thuh"], "2.3 13.3 14.6": ["portentousness"], "-2.1 -3.3 5.7": ["amt"], "6.0 14.3 6.9": ["medicore"], "7.0 14.9 6.1": ["uncommanded"], "10.3 -4.8 17.2": ["coa"], "9.2 -1.8 15.3": ["polybags"], "12.6 8.0 1.0": ["narcocorrido"], "0.6 11.3 20.4": ["subalpine"], "-4.8 -0.8 -1.6": ["assesed"], "18.0 -3.2 -5.0": ["refurbisher"], "8.2 11.7 9.0": ["cattily"], "5.4 -2.5 2.8": ["underpriviledged"], "-0.4 5.8 6.1": ["jak"], "7.5 6.4 13.7": ["enviornmental"], "9.5 8.3 22.9": ["tealeaves"], "10.6 8.9 11.8": ["transcendentally"], "6.7 5.2 7.6": ["damit"], "17.8 10.8 13.5": ["boohoo"], "5.1 32.7 10.2": ["treacheries"], "5.3 7.6 11.3": ["multipathing"], "10.1 7.9 33.3": ["takahe"], "6.1 10.2 20.1": ["snowpants"], "4.4 9.8 13.9": ["wuk"], "10.7 4.8 26.8": ["weck"], "-1.5 11.3 9.2": ["cavils"], "2.4 4.5 12.2": ["seismograms"], "13.6 15.7 10.9": ["unpleasing"], "8.2 10.6 15.5": ["tottenham"], "10.1 12.4 10.7": ["witih", "vulgarization"], "1.7 -5.1 9.9": ["morocco"], "-4.0 3.7 5.6": ["perfluorocarbons"], "5.2 6.6 6.9": ["coplanar"], "6.1 13.3 21.6": ["shepard"], "6.1 6.1 14.6": ["pelikula"], "15.5 11.5 15.4": ["boltholes"], "0.3 19.2 5.1": ["somethign"], "-0.4 2.3 10.1": ["nonclassroom"], "4.9 16.9 8.1": ["metacognition"], "0.9 7.8 10.7": ["cedula"], "17.3 -7.8 10.4": ["foodcourt"], "-2.8 14.6 12.0": ["eosinophilic"], "7.7 13.9 21.4": ["gumline"], "13.7 19.9 7.8": ["mometum"], "0.7 6.2 6.4": ["penghulus"], "14.8 4.4 23.5": ["bulbul"], "5.8 4.7 9.8": ["miscoding"], "13.6 0.3 22.0": ["palazzi"], "6.8 5.1 6.7": ["succcess"], "4.9 4.7 16.9": ["gau"], "1.0 10.2 13.9": ["connubial"], "13.5 4.1 16.9": ["kuai"], "0.7 1.8 4.3": ["tomeet"], "-2.4 4.1 4.3": ["entspricht"], "10.7 1.5 13.3": ["fezzes"], "6.6 19.7 10.0": ["hatton"], "19.7 7.5 25.5": ["smorgasbords"], "-5.7 6.1 13.5": ["landuse"], "5.0 10.4 9.4": ["radiologically"], "-2.1 9.7 4.7": ["overtreating"], "11.5 3.4 32.8": ["shortbreads"], "14.0 11.4 27.0": ["cants"], "2.8 0.9 21.9": ["laddus"], "4.3 14.4 6.5": ["forswore"], "6.1 5.8 -0.9": ["combustors"], "3.0 6.7 7.2": ["electrodeposition"], "-0.6 8.1 14.6": ["fermentable"], "12.2 9.9 15.5": ["flagellin"], "1.7 1.7 2.8": ["leadin"], "4.7 -0.4 9.6": ["parklet"], "-1.2 12.7 11.3": ["downtrending"], "13.2 13.0 13.3": ["facinating"], "5.0 21.9 3.7": ["differance"], "0.2 9.5 1.2": ["progovernment"], "3.8 0.8 6.3": ["wheelsets"], "13.5 10.3 9.9": ["metabolome"], "11.9 5.2 13.7": ["sizer"], "-2.3 13.3 5.3": ["intrapersonal"], "7.8 12.8 6.8": ["buisnesses", "adelante"], "4.5 -2.3 5.5": ["arzoxifene"], "3.1 8.1 3.1": ["viele"], "8.5 10.3 -0.7": ["subcribers"], "8.6 24.2 2.7": ["pigheadedness"], "-0.5 15.7 -5.1": ["mantain"], "0.2 6.9 4.1": ["erbium"], "8.8 4.0 24.1": ["undyed"], "10.3 10.0 22.0": ["blastema"], "0.8 6.2 2.0": ["ipoints"], "-2.8 14.2 14.1": ["iyo"], "2.0 2.0 -3.2": ["synergizes"], "20.3 6.3 17.3": ["putti"], "5.9 2.2 40.6": ["aquaculturists"], "2.2 5.4 11.6": ["tse"], "16.4 2.0 12.2": ["unfreezes"], "2.9 -0.8 -0.3": ["psychobiology"], "16.2 3.5 1.6": ["bladeless"], "17.2 7.0 14.3": ["aquiver"], "5.8 8.1 5.2": ["subeditors"], "10.6 7.8 35.0": ["bacons"], "11.2 13.2 26.0": ["backstay"], "6.6 0.3 3.4": ["ralled"], "10.3 12.5 9.2": ["rasterization"], "16.1 26.9 9.9": ["lebensraum"], "6.1 11.6 9.8": ["namer", "sumithrin"], "19.3 14.6 5.6": ["boldy"], "0.7 13.8 1.7": ["rishis"], "6.9 9.2 18.8": ["waterbuck"], "14.5 7.3 5.2": ["doodlings"], "9.6 16.9 18.9": ["questioningly"], "2.6 23.2 13.5": ["quartermasters"], "18.8 3.5 17.5": ["openwork"], "-5.9 11.7 1.1": ["inseperable"], "4.7 20.4 1.4": ["dislikeable"], "5.8 2.2 8.3": ["whie"], "1.4 16.7 22.2": ["sachem"], "5.3 20.5 8.0": ["porousness"], "2.9 9.7 10.8": ["monsignors"], "-2.3 -7.1 0.2": ["progra"], "3.7 7.0 12.5": ["stitutions"], "11.4 1.7 7.7": ["hough"], "4.7 0.6 13.4": ["pulpmills"], "3.0 12.5 11.1": ["pyroprocessing"], "6.1 6.8 16.5": ["brunching"], "-3.5 10.9 -0.3": ["nonparties"], "0.2 18.5 8.4": ["explicative"], "3.2 14.0 10.7": ["karenge"], "-10.4 -1.9 2.6": ["roadrace"], "15.9 7.1 14.4": ["ramadas"], "-3.2 -0.5 2.8": ["cott"], "17.3 7.0 38.4": ["cooter"], "-7.3 0.8 0.7": ["cpr"], "14.1 10.6 5.7": ["picoliter"], "9.2 34.8 5.1": ["saddam"], "2.3 13.5 6.9": ["hospitability"], "1.5 9.7 11.9": ["klaar"], "4.9 19.3 9.8": ["militar"], "10.0 17.0 14.3": ["epicness"], "11.4 9.8 25.1": ["houmous"], "14.7 12.9 13.0": ["parachuters"], "-0.6 4.0 7.2": ["chldren"], "1.4 8.4 12.3": ["vbs"], "-3.7 1.1 6.8": ["ginner"], "18.5 16.4 15.5": ["scabbards"], "6.3 10.4 13.0": ["endothermic"], "11.9 16.8 5.4": ["vacuously"], "5.4 9.5 -2.0": ["tolars"], "8.0 3.2 -0.1": ["geht"], "10.3 -6.0 2.4": ["novo"], "14.4 12.6 10.7": ["viscount"], "2.0 1.8 8.9": ["clavichord"], "2.2 13.0 12.6": ["keyway"], "4.6 5.8 4.4": ["musican"], "11.5 21.7 8.0": ["hegemonies"], "6.1 15.8 9.3": ["libertinism"], "3.5 5.3 2.9": ["inaguration"], "11.1 30.6 4.5": ["irreducibly"], "2.8 11.7 14.2": ["thiols"], "9.3 20.0 18.7": ["girt"], "1.2 6.0 0.3": ["tthat"], "-1.0 1.0 14.6": ["garnacha"], "-4.7 -6.0 1.8": ["cated"], "-0.8 14.6 5.4": ["maqam"], "2.8 2.0 3.9": ["acitivities"], "-3.5 13.0 8.7": ["settable"], "19.4 7.2 18.4": ["woofed"], "10.5 13.7 9.0": ["perrenial"], "7.1 8.5 11.0": ["activitiy"], "-4.3 1.5 10.9": ["serdes"], "2.3 -0.7 -0.4": ["aspartate"], "16.7 9.3 25.0": ["sporks"], "5.9 7.0 14.0": ["figurations"], "-6.0 1.2 7.8": ["rumspringa"], "6.4 19.5 9.6": ["defilers"], "0.6 13.0 -1.1": ["hospitalise"], "8.4 9.8 7.2": ["nuestra"], "4.9 5.6 2.0": ["andf"], "12.9 14.2 13.7": ["passeth"], "2.7 8.9 5.4": ["pedophiliac"], "3.8 16.9 17.9": ["subsistent"], "7.9 9.8 13.3": ["troopergate"], "3.7 6.3 19.3": ["argent"], "10.4 12.3 18.0": ["ghoulishness"], "1.4 19.4 9.8": ["fillibuster"], "-1.1 8.1 8.3": ["procalcitonin"], "-3.7 2.0 19.7": ["collagens"], "8.6 23.2 4.7": ["revanchism"], "2.1 15.3 4.9": ["inconclusiveness"], "-1.1 -0.3 -3.4": ["ergonomist"], "7.9 -0.3 11.5": ["stanley"], "-6.5 11.2 9.5": ["ruth"], "10.8 22.5 12.6": ["townsperson"], "7.3 17.1 10.5": ["abed"], "9.0 1.7 32.4": ["moules"], "2.9 1.3 1.6": ["sexploits"], "6.6 0.5 -1.0": ["whihc"], "12.9 18.7 14.5": ["sayers"], "5.5 5.5 5.7": ["hypermedia"], "0.2 4.6 10.2": ["loadspace"], "6.6 10.9 2.1": ["childre"], "-2.2 4.1 18.7": ["farmwork"], "-8.6 6.2 11.7": ["districted"], "9.5 21.1 17.7": ["crip"], "6.5 38.6 12.3": ["ltte"], "-3.3 6.2 8.8": ["punitives"], "-0.8 12.9 4.5": ["unpegged"], "1.9 12.0 8.7": ["politica"], "9.8 6.9 8.5": ["perambulating"], "-1.0 16.9 10.9": ["denge"], "25.2 15.6 14.9": ["greedheads"], "13.5 12.0 19.1": ["tonguing"], "-0.5 7.6 11.4": ["jhuggi"], "8.9 18.2 12.9": ["inflowing"], "8.4 11.0 17.3": ["sistah"], "3.0 6.2 7.7": ["impliment"], "10.9 10.9 15.8": ["crozier"], "11.5 12.0 33.8": ["murrelets"], "-5.5 2.6 11.6": ["waybills"], "0.3 14.6 6.6": ["canticle"], "6.7 14.7 7.7": ["gallingly"], "8.7 8.9 28.5": ["penstemons"], "6.1 5.3 3.1": ["aerostructure"], "18.6 20.5 10.8": ["oooooh"], "15.8 7.9 1.5": ["nextgen"], "-0.5 8.8 30.0": ["tomcod"], "4.6 33.7 7.3": ["bloodiness"], "16.2 5.4 14.0": ["aound"], "3.4 5.5 6.4": ["implanter"], "7.2 6.5 24.3": ["coasteering"], "13.4 17.7 22.2": ["clew"], "1.9 -3.6 4.3": ["ehr"], "15.7 14.6 9.8": ["overdesigned"], "7.3 2.0 15.8": ["porphyritic"], "10.9 17.1 33.6": ["daphnia"], "14.4 12.8 13.5": ["oik"], "2.7 2.3 -1.1": ["andbusiness"], "6.2 4.3 6.7": ["expeditor"], "15.3 15.2 14.9": ["slickrock"], "4.6 4.2 6.5": ["hazings"], "8.2 3.7 8.3": ["ocho"], "11.0 29.0 13.4": ["fissiparous"], "-0.1 6.1 11.3": ["coagulants"], "14.0 12.3 21.4": ["culm"], "8.3 11.0 14.0": ["smallscale"], "7.9 5.2 22.0": ["lobo"], "15.0 12.3 1.5": ["genuis"], "-9.1 -0.8 3.3": ["homebirths"], "2.3 1.2 34.0": ["bearnaise"], "-0.1 2.3 5.9": ["shortline"], "1.5 -2.7 20.5": ["soyaoil"], "16.5 9.9 14.2": ["bevelled"], "10.7 10.4 1.5": ["unintegrated"], "5.1 4.8 4.1": ["beatmakers"], "10.4 11.2 11.3": ["moer"], "4.1 11.2 4.0": ["disputations"], "13.3 12.3 14.8": ["italians"], "3.5 17.6 11.7": ["askaris"], "7.8 21.1 12.8": ["fraid"], "-2.7 15.0 2.0": ["undedicated"], "16.2 4.1 35.6": ["kob"], "20.6 8.6 27.5": ["tarsier"], "8.1 12.2 6.7": ["ticketmate"], "12.6 10.9 11.5": ["jos"], "8.4 15.8 13.1": ["wayyyy"], "-7.0 8.8 -7.2": ["misadvised"], "-3.1 4.2 10.8": ["efalizumab"], "10.4 12.1 10.0": ["unsnapped"], "6.7 19.3 14.5": ["pinche"], "15.3 20.7 3.6": ["cyberespionage"], "17.0 5.9 13.3": ["newsie"], "-3.5 2.3 0.1": ["subvented"], "4.9 13.4 11.0": ["gid"], "11.6 17.5 13.7": ["nazar"], "4.9 17.8 8.1": ["postmodernity"], "0.5 2.7 5.7": ["rufinamide"], "10.2 12.5 11.0": ["sooooooooo"], "0.8 14.8 -1.2": ["illumines"], "9.3 -2.6 6.1": ["virt"], "-2.4 -5.0 3.5": ["lpm"], "-10.1 9.0 7.2": ["dyslipidaemia"], "2.6 14.8 3.1": ["unauditable"], "5.7 13.9 15.4": ["corpuscles"], "14.8 3.2 5.4": ["wrongfooting"], "13.2 16.2 13.5": ["guiltlessly"], "16.9 14.6 22.1": ["moondust"], "8.6 16.5 12.5": ["antineutrinos"], "5.5 11.2 8.3": ["beatboxers"], "3.2 4.7 3.8": ["lx"], "4.6 2.8 11.0": ["loungy"], "-0.6 5.4 7.1": ["keung"], "15.7 11.5 12.9": ["bourgeoise"], "12.0 9.5 16.5": ["stiffener"], "8.4 8.2 13.9": ["donner"], "2.2 3.1 17.3": ["richards"], "4.6 22.2 12.2": ["offbalance"], "16.2 4.4 19.0": ["filigrees"], "16.8 14.8 17.8": ["sidewise"], "5.6 3.0 12.8": ["rutin"], "12.3 11.9 25.3": ["tahr"], "0.6 19.2 9.1": ["boundry"], "16.9 7.8 -3.3": ["bankrutpcy"], "5.5 -2.9 8.3": ["bolivianos"], "-4.7 -0.3 -4.0": ["advisements"], "12.6 -1.0 0.7": ["folllowing"], "9.7 29.6 4.9": ["interferers"], "2.0 10.7 7.9": ["homonymous"], "10.2 13.7 8.9": ["gauranteed"], "22.2 7.5 13.5": ["chuff"], "-0.8 2.9 12.4": ["horsewomen"], "8.8 2.9 26.0": ["parantha"], "7.6 5.4 9.4": ["waz"], "26.4 9.2 4.9": ["nationalises"], "4.2 0.4 -1.4": ["tastemaking"], "7.8 6.6 4.0": ["connectivities"], "9.8 6.0 4.4": ["vetter"], "16.8 22.8 13.8": ["keisters"], "10.5 24.8 6.7": ["distruction"], "12.6 11.4 23.3": ["masticate"], "8.7 17.3 18.0": ["mugginess"], "12.7 1.4 11.5": ["hilton"], "10.3 8.1 7.1": ["tropicalia"], "5.4 -1.6 18.2": ["flr"], "7.9 5.3 15.4": ["raymond"], "2.7 26.2 3.6": ["fallaciously"], "8.6 15.7 13.9": ["nanoantennas"], "1.8 21.2 4.1": ["ceasfire"], "8.2 22.6 1.7": ["prowar"], "-8.2 -5.8 10.7": ["sesson"], "0.6 14.4 12.5": ["breakings"], "5.5 11.7 12.1": ["riskily"], "11.5 13.5 18.0": ["peristalsis"], "-8.0 6.2 5.1": ["untimeliness"], "11.6 9.7 19.0": ["streptavidin"], "6.2 6.1 6.9": ["quebec"], "1.2 13.8 18.6": ["xeric"], "14.4 2.8 12.6": ["guilder"], "0.6 11.3 4.2": ["parliamentarism"], "8.2 5.1 11.8": ["cutes"], "1.0 13.0 5.9": ["jana"], "6.9 5.6 22.3": ["bassets"], "-1.2 13.7 11.1": ["portraitists"], "7.1 10.5 42.6": ["deveined"], "13.0 10.9 7.9": ["fying"], "3.6 10.2 2.8": ["kombis"], "10.0 7.9 12.6": ["unamusing"], "12.2 7.5 7.9": ["gaboxadol"], "-3.3 -3.8 7.2": ["preprofessional"], "-2.1 12.5 8.8": ["pneumococci"], "7.9 1.5 6.3": ["qtrs"], "-7.4 4.2 3.2": ["froglogic"], "13.8 2.4 11.9": ["superagency"], "5.3 6.6 16.9": ["ornamentations"], "17.7 -5.6 -5.4": ["unvieled"], "11.9 4.7 9.8": ["weatherproofed"], "6.5 27.7 7.0": ["antisemite"], "1.4 10.7 20.7": ["albarino"], "1.7 14.8 15.3": ["lymphatics"], "6.6 5.2 10.8": ["moonlighters"], "6.9 23.2 11.0": ["playaction"], "2.4 1.4 6.9": ["gzip"], "4.4 -4.7 15.1": ["chewables"], "6.6 8.1 33.0": ["cheeseballs"], "12.1 23.7 13.3": ["unbendable"], "-2.2 12.2 6.5": ["uddin"], "-2.5 6.0 0.1": ["ourcustomers"], "10.8 4.0 13.9": ["unrecyclable"], "9.6 8.3 38.8": ["ratfish"], "12.1 10.9 14.7": ["sundecks"], "7.7 1.9 20.8": ["handymax"], "3.6 10.5 10.9": ["rainchecks"], "-4.3 5.3 11.6": ["topscore"], "18.2 19.2 25.4": ["sharking"], "14.9 10.4 14.3": ["howlin"], "0.5 -2.7 9.1": ["boyd"], "12.4 9.5 4.7": ["xkcd"], "17.7 3.6 15.3": ["poptastic"], "17.9 15.1 18.2": ["thor"], "18.1 16.3 6.2": ["microrobots"], "8.2 10.7 21.2": ["hau"], "11.2 10.5 28.8": ["dongs"], "18.6 4.6 11.7": ["babyfood"], "20.5 12.6 18.9": ["nightscape"], "3.7 2.2 -0.1": ["movables"], "6.5 8.4 16.3": ["spock"], "3.9 3.5 7.5": ["subproject"], "5.5 2.8 9.7": ["samuel"], "12.6 8.0 6.3": ["grrrl"], "-2.2 9.5 5.4": ["autofluorescence"], "13.5 0.1 14.6": ["bolide"], "15.8 6.4 28.7": ["cruet"], "7.9 4.4 8.1": ["seatstays"], "3.4 35.3 8.9": ["teamplay"], "3.4 -1.5 5.0": ["dublin"], "5.6 9.4 12.8": ["dolomitic"], "-2.5 9.6 7.3": ["batterymates"], "-6.1 -9.2 3.4": ["antepartum"], "8.5 -1.4 6.9": ["motorbiking"], "10.4 6.1 29.9": ["chargrill"], "-5.4 6.1 11.8": ["peterson"], "10.6 29.9 17.2": ["hider"], "-9.7 -1.1 8.9": ["campership"], "15.9 9.1 11.2": ["iconostasis"], "8.8 8.7 11.5": ["struttin"], "8.2 8.5 16.0": ["flightiness"], "3.5 8.0 4.4": ["hexogen"], "14.2 9.7 13.7": ["grooviness"], "11.3 15.1 21.4": ["kneedrop"], "11.7 10.7 17.6": ["chinless"], "-1.1 2.4 17.3": ["pasar"], "7.1 14.2 9.1": ["stockpilers"], "14.5 15.1 19.6": ["porking"], "15.5 8.4 23.8": ["stewpot"], "7.2 1.3 -2.0": ["riden"], "-4.3 6.1 8.0": ["neuroblastomas"], "8.6 10.3 8.3": ["radiosonde"], "20.6 9.5 10.4": ["hedgie"], "27.2 13.8 14.2": ["kapow"], "2.7 -0.3 12.5": ["cyclamate"], "5.9 1.1 2.2": ["impresive"], "8.6 15.8 11.6": ["bromances"], "8.7 16.3 6.0": ["aborning"], "4.1 1.7 6.6": ["nore"], "3.5 15.4 13.4": ["overdevelop"], "8.8 12.2 6.1": ["supersolid"], "6.2 -2.5 8.2": ["multisector"], "-3.0 3.7 10.5": ["swineflu"], "9.3 17.6 14.5": ["dermotcole"], "5.9 2.3 12.9": ["staycationers"], "5.8 6.4 8.7": ["presciption"], "0.8 15.2 7.6": ["educable"], "11.8 7.9 7.6": ["magnetotail"], "17.1 18.0 22.7": ["whacker"], "-5.8 32.8 6.7": ["airwomen"], "10.9 22.9 10.7": ["posthuman"], "-7.1 11.7 -0.3": ["methacholine"], "-3.3 13.7 -0.6": ["underated"], "-5.2 11.4 -1.4": ["adductors"], "-2.1 0.3 8.7": ["nondiabetics"], "5.5 9.1 12.4": ["touranment"], "-0.3 -3.3 7.7": ["revisted"], "12.8 4.0 8.5": ["malternatives"], "18.7 9.7 10.5": ["reskinned"], "-1.1 6.8 14.8": ["mundu"], "-9.5 -2.8 11.7": ["leadtimes"], "3.6 17.0 17.5": ["antigrowth"], "19.3 16.6 11.8": ["ftw"], "5.5 18.1 8.6": ["sanctimoniousness"], "-7.8 10.0 3.4": ["resuscitations"], "6.1 3.3 3.1": ["reste"], "6.8 9.9 14.1": ["godsends"], "8.7 18.6 24.8": ["icefield"], "2.8 21.3 10.4": ["trickeration"], "11.6 28.3 3.7": ["beastliness"], "6.4 7.2 4.0": ["threegame"], "13.7 6.4 34.2": ["ladyfinger"], "5.3 4.7 18.8": ["pelleting"], "6.9 -9.2 16.3": ["yuen"], "-6.3 0.8 7.2": ["bers"], "15.8 1.9 8.4": ["superwide"], "8.8 13.1 10.8": ["nolonger"], "8.3 7.5 16.4": ["mazurka"], "1.3 1.3 45.1": ["baymen"], "6.6 -6.5 -2.6": ["ternational"], "9.8 12.7 13.0": ["whinnies"], "-2.9 5.1 0.7": ["lity"], "-1.1 10.8 3.9": ["homosexually"], "4.1 8.7 3.0": ["bayern"], "2.5 -9.6 5.6": ["nf"], "-8.0 12.2 3.7": ["outpolls"], "10.3 -0.8 14.8": ["fcc"], "15.3 13.8 8.7": ["motorik"], "5.4 1.6 2.8": ["plys"], "8.2 14.5 22.1": ["oocysts"], "10.4 5.0 16.7": ["hipbones"], "3.8 13.5 5.2": ["kerning"], "14.5 4.8 10.4": ["sunhats"], "14.0 4.4 17.7": ["wailer"], "9.1 5.0 27.2": ["kamut"], "-6.0 18.0 -8.7": ["exculpated"], "3.8 11.1 -2.0": ["tweeple"], "20.1 2.4 22.1": ["looky"], "11.6 8.1 30.8": ["sinensis"], "8.0 5.1 1.2": ["kickaround"], "4.3 12.5 9.1": ["hogi"], "6.2 15.1 23.3": ["vervain"], "13.5 4.2 30.6": ["imu"], "11.6 17.3 25.2": ["decomposers"], "4.1 4.0 6.9": ["enery"], "5.9 -5.3 -1.7": ["supranationals"], "16.2 19.2 8.8": ["agilely"], "1.9 27.2 -3.0": ["carnages"], "3.1 12.3 11.3": ["biorhythm"], "12.5 27.6 10.9": ["overdog"], "5.8 24.0 24.4": ["treestands"], "12.1 6.7 20.5": ["midcontinent"], "6.1 4.0 5.0": ["imap"], "-2.0 -5.0 6.5": ["prosthodontist"], "9.4 17.6 9.6": ["malfeasant"], "3.1 12.2 3.9": ["legatee"], "-7.9 5.9 8.6": ["trem"], "6.5 19.8 12.3": ["pendejo"], "3.5 12.1 16.9": ["hydrophobicity"], "9.0 19.7 7.2": ["traceroute"], "22.3 6.2 7.9": ["advertainment"], "10.4 14.2 1.0": ["dosnt"], "16.1 12.9 10.4": ["enshrouds"], "7.3 13.2 5.2": ["contenting"], "9.8 16.3 6.2": ["flummoxes"], "9.9 13.0 18.3": ["vaporetto"], "-2.1 20.7 6.9": ["reconsolidate"], "4.6 0.7 0.9": ["nateglinide"], "-4.8 14.9 4.4": ["acupoints"], "2.6 7.2 1.9": ["zumo"], "7.5 11.1 2.6": ["rededicates"], "5.1 1.7 3.9": ["internacional"], "6.4 4.4 11.5": ["gbp"], "17.3 10.1 12.6": ["investers"], "2.3 0.0 17.6": ["flatwork"], "5.6 9.5 2.0": ["behaviourist"], "6.5 14.6 6.7": ["naifs"], "10.3 10.1 9.5": ["shemozzle"], "3.6 3.7 10.1": ["allaround"], "14.1 24.0 18.0": ["supercarriers"], "0.6 1.3 2.9": ["frovatriptan"], "1.9 13.7 13.7": ["incomer"], "-0.7 -0.2 5.0": ["kendras"], "3.8 8.4 11.4": ["olivia"], "8.5 11.8 27.9": ["forsythias"], "3.0 1.9 15.2": ["basi"], "6.8 7.0 8.0": ["nearterm"], "8.3 -1.1 14.9": ["guayaberas"], "11.7 6.0 7.1": ["deindustrialisation"], "-5.8 4.6 4.1": ["thromboses"], "-1.8 1.8 10.4": ["romney"], "3.9 4.4 11.1": ["pessary"], "11.5 14.4 10.2": ["sleazebags"], "4.3 -0.5 9.0": ["aree"], "16.5 11.7 17.9": ["sourpusses"], "6.6 1.0 6.2": ["roughstock"], "12.6 12.6 22.2": ["icey"], "5.5 13.4 9.3": ["unabating"], "9.3 -1.2 13.7": ["petits"], "18.5 3.7 18.3": ["dowagers"], "9.2 14.0 6.3": ["brainwork"], "-0.1 2.4 4.6": ["tomans"], "8.5 14.5 32.2": ["crossbills"], "3.0 14.1 16.4": ["retrotransposons"], "5.8 9.6 -1.8": ["apear"], "8.7 20.3 -0.2": ["freindly"], "17.8 27.4 12.5": ["blackguard"], "6.3 7.7 -1.1": ["tubelights"], "7.6 18.7 17.0": ["carder"], "10.0 -7.3 11.9": ["slighlty"], "-2.5 4.6 12.5": ["rhyolites"], "16.7 3.8 7.4": ["businessess"], "10.4 14.8 12.0": ["newscasting"], "8.4 13.4 6.7": ["earmuff"], "9.4 11.0 3.4": ["uncowed"], "-3.2 37.2 -4.2": ["unembedded"], "10.0 4.8 16.0": ["avoir"], "12.8 7.2 14.0": ["oversupplies"], "11.0 20.8 8.5": ["affronting"], "14.1 14.3 4.8": ["microsensors"], "8.3 17.4 12.1": ["mesothelium"], "8.8 -6.3 0.3": ["proofers"], "5.6 4.9 4.5": ["urpmi"], "12.2 11.6 13.4": ["digged"], "-0.4 11.9 19.5": ["streambank"], "2.5 8.1 -4.0": ["nonpracticing"], "16.1 20.7 -0.3": ["embeded"], "5.7 7.6 10.8": ["moviehouses"], "12.1 15.0 14.5": ["townscapes"], "-3.6 0.9 2.1": ["plugfests"], "0.3 22.2 5.9": ["disempowers"], "5.6 0.2 7.4": ["howver"], "-0.5 7.1 15.6": ["atu"], "-2.6 2.2 4.0": ["lia"], "8.4 6.4 12.6": ["wv"], "6.6 7.7 13.7": ["freebee"], "5.0 10.9 12.7": ["overprotection"], "3.4 -1.7 13.2": ["curatives"], "7.5 17.1 8.8": ["batmen"], "3.2 24.1 9.0": ["repulsiveness"], "9.5 -5.1 0.7": ["callled"], "6.2 5.4 4.1": ["suffixed"], "10.4 23.8 5.0": ["purblind"], "-0.5 5.0 4.5": ["criminogenic"], "16.2 11.1 14.7": ["starlike"], "-0.7 -4.7 1.8": ["preleasing"], "-1.4 3.6 6.7": ["ostarine"], "3.1 0.5 14.9": ["proppants"], "-1.7 6.6 -0.0": ["rian"], "4.2 5.2 10.1": ["fundas"], "14.8 7.7 9.0": ["lorida"], "7.0 27.2 4.8": ["defencive"], "-7.4 13.1 3.4": ["fanpost"], "0.1 5.0 10.9": ["lards"], "13.4 -2.5 13.9": ["divs"], "12.9 -4.9 13.8": ["reclaimers"], "1.3 15.8 9.0": ["colleage"], "3.0 9.4 6.2": ["oversite"], "-1.7 15.6 7.5": ["issueless"], "10.1 6.2 8.1": ["mandapam"], "2.8 -4.0 12.5": ["nimesulide"], "6.2 3.0 15.3": ["endplate"], "6.8 3.2 17.0": ["neaten"], "9.9 4.3 14.1": ["clangorous"], "10.4 11.9 6.5": ["overblow"], "3.2 9.4 7.2": ["dlavoie"], "5.3 2.9 8.1": ["meetinghouses"], "11.6 23.4 16.7": ["wimpiness"], "6.7 -3.8 2.5": ["deve"], "-10.1 9.7 9.6": ["optionals"], "14.8 11.2 20.7": ["ridable"], "5.9 14.2 7.8": ["answerer"], "3.7 8.0 9.2": ["flyglobespan"], "8.4 7.9 12.4": ["yellin"], "8.2 2.7 15.8": ["paleobiology"], "20.9 -0.6 13.1": ["bouffants"], "-8.0 10.7 7.2": ["concered"], "10.0 7.0 11.8": ["moonman"], "2.2 17.1 4.9": ["antireligious"], "17.3 11.0 4.8": ["experiement"], "-0.0 0.4 6.3": ["polysorbate"], "2.6 4.9 -4.7": ["seinen"], "-0.2 13.9 4.6": ["disruptiveness"], "12.9 5.3 15.3": ["netlet"], "1.0 13.4 6.9": ["parishoner"], "2.6 11.8 15.8": ["ganun"], "12.1 26.3 18.3": ["aristocracies"], "14.5 22.5 8.7": ["faggy"], "21.0 26.7 16.0": ["bodiless"], "-0.4 -6.0 12.1": ["clases"], "8.5 7.0 18.3": ["herdmates"], "7.3 5.9 17.2": ["charros"], "7.2 6.1 10.9": ["nosotros"], "5.1 1.8 4.3": ["algunos"], "5.0 5.0 5.5": ["everynight"], "14.9 4.2 9.9": ["trunkful"], "-0.7 2.6 12.8": ["boppish"], "15.0 7.0 9.6": ["fullblown"], "10.6 17.6 10.7": ["posterizing"], "16.8 11.6 9.9": ["tempermental"], "18.8 10.6 8.5": ["nissan"], "-2.3 16.4 2.1": ["probelms"], "-1.8 9.7 7.8": ["prosecutrix"], "3.5 8.7 11.8": ["slowcore"], "-8.6 -3.2 1.8": ["podcasted"], "4.8 6.4 11.3": ["cna"], "6.9 7.2 5.7": ["tradeport"], "5.6 5.5 6.8": ["bhavan"], "-3.8 9.6 3.6": ["necrotizing"], "16.3 9.7 25.9": ["tufa"], "1.6 8.4 15.8": ["dts"], "13.9 -2.1 3.3": ["concessionaries"], "-1.3 11.1 4.3": ["functionalize"], "3.6 19.8 6.0": ["intradivision"], "12.9 10.8 13.6": ["mooches"], "12.7 6.2 14.3": ["dreich"], "-1.6 9.8 2.0": ["azar"], "9.5 10.7 2.3": ["blogsites"], "13.4 7.6 17.7": ["stepstool"], "15.2 9.1 9.8": ["tootle", "funsters"], "4.4 2.3 6.4": ["superlattice"], "18.3 9.0 11.5": ["recutting"], "9.8 1.4 10.6": ["garbagemen"], "2.1 10.5 5.8": ["oater"], "16.5 9.2 19.4": ["wittle"], "5.4 15.8 7.8": ["roistering"], "-5.1 22.6 5.1": ["violance"], "13.1 26.9 16.1": ["hazarding"], "3.7 3.5 13.1": ["wmt"], "-1.6 -2.8 2.6": ["gastroenterological"], "3.9 15.5 2.7": ["somehting"], "13.7 16.9 7.4": ["phoniest"], "2.7 18.4 17.6": ["shrublands"], "0.7 14.7 1.8": ["offroading"], "14.0 9.4 13.7": ["freightliner"], "0.3 15.9 24.7": ["humous"], "2.0 7.1 10.5": ["laybys"], "-1.4 10.3 10.7": ["holden"], "-3.2 -5.0 1.5": ["rubels"], "1.0 14.3 12.1": ["fk"], "18.0 19.1 6.2": ["enmeshing"], "18.6 12.8 18.6": ["reviver"], "12.4 4.9 21.7": ["dama"], "7.4 14.4 14.0": ["wsaz"], "8.2 8.0 0.1": ["sipgate"], "5.8 25.6 13.0": ["corruptor"], "11.9 7.8 20.1": ["rojo"], "13.0 16.3 14.6": ["larrikins"], "10.3 14.8 21.9": ["ralph"], "-9.1 -5.4 -3.6": ["preceptorship"], "-0.1 9.5 11.9": ["jetskiing"], "18.1 12.5 5.8": ["flightdeck"], "1.1 9.2 15.8": ["nestin"], "25.8 9.7 2.4": ["gobal"], "11.7 19.2 15.9": ["connivers"], "1.9 11.5 14.2": ["interestingness"], "15.2 -8.8 -0.9": ["announcedtoday"], "4.1 12.0 8.2": ["unbackable"], "2.6 4.4 4.9": ["rotable"], "-1.1 7.7 12.8": ["cholesterols"], "18.8 5.5 16.5": ["mudflaps"], "-0.9 4.9 19.6": ["lockmaster"], "3.5 -8.5 -1.0": ["inlcuded"], "13.3 2.9 16.5": ["ramblin"], "3.9 1.0 6.5": ["presorted"], "9.6 -0.3 5.9": ["busi"], "5.7 6.9 12.5": ["nulla"], "8.8 14.2 11.6": ["bollox"], "-4.9 3.4 -1.9": ["precipitator"], "-13.5 9.2 13.2": ["transiency"], "10.6 5.3 3.5": ["radiopharmacies"], "-2.5 4.3 6.8": ["unticketed"], "20.0 10.6 14.8": ["abseilers"], "-6.2 9.7 7.3": ["studiousness"], "20.5 13.3 7.4": ["rampway"], "17.8 0.3 14.0": ["balconied"], "7.2 9.8 13.2": ["snowguns"], "13.6 13.1 39.4": ["tunicate"], "14.7 18.0 14.5": ["sumbitch"], "5.1 2.4 1.7": ["subeditor"], "6.9 2.3 7.8": ["moneylist"], "16.7 -1.8 12.1": ["worktables"], "-13.5 -0.1 5.0": ["presentments"], "9.6 -0.6 22.4": ["biopark"], "10.2 19.0 8.1": ["preclusive"], "20.5 8.7 9.4": ["chuckleheads"], "6.6 -2.9 20.6": ["getai"], "5.0 0.0 5.4": ["tesofensine"], "12.1 1.0 18.6": ["gilets"], "5.2 1.4 17.7": ["suedes"], "19.5 27.0 16.9": ["ragdolls"], "-1.8 4.6 3.5": ["subdural"], "0.5 0.8 1.9": ["devrait"], "-2.6 -0.2 5.9": ["crinobulin"], "16.7 26.4 9.0": ["launchpads"], "-1.5 8.4 12.9": ["misfielded"], "5.6 -1.4 2.8": ["isan"], "9.5 7.4 22.4": ["restaraunts"], "11.2 11.0 9.9": ["standover"], "-3.0 21.0 14.2": ["firewise"], "5.9 9.2 12.5": ["greenskeepers"], "4.8 16.3 23.0": ["crosse"], "7.5 8.9 -2.9": ["theleader"], "9.7 2.0 14.6": ["kirana"], "1.8 15.8 7.1": ["rivetingly"], "12.6 5.8 10.1": ["ards"], "6.4 5.9 11.3": ["awn"], "-6.1 10.5 6.3": ["virement"], "0.2 16.6 27.6": ["freedivers"], "-2.1 12.2 8.5": ["dono"], "14.7 19.7 15.3": ["karmically"], "26.4 18.0 18.6": ["treelike"], "1.9 1.2 8.6": ["mineralogist"], "7.3 0.2 7.2": ["deathcare"], "7.6 17.9 9.8": ["obamacare"], "10.5 5.9 -2.0": ["futur"], "6.1 8.6 8.5": ["defo"], "13.4 11.2 28.0": ["tuberous"], "2.5 6.0 -4.2": ["repond"], "-0.5 2.9 28.1": ["splittail"], "0.3 7.3 3.5": ["absorptions"], "19.6 23.5 8.7": ["recolonisation"], "12.6 12.2 35.0": ["redstart"], "5.6 0.8 1.2": ["provice"], "5.8 3.1 18.6": ["staches"], "5.1 3.0 -3.1": ["cout"], "4.7 0.8 7.1": ["concessioner"], "19.1 7.1 9.3": ["spraypainting"], "5.7 13.6 8.5": ["overborrowing"], "-1.2 8.2 2.8": ["workpapers"], "14.8 12.0 8.1": ["neighing"], "11.1 14.6 7.0": ["gabbers"], "10.2 6.1 12.0": ["yuppified"], "19.8 -1.5 4.5": ["indus"], "4.1 7.7 24.1": ["ketupat"], "20.4 5.4 26.2": ["zebu"], "-0.3 8.9 10.2": ["kab"], "6.2 15.8 18.7": ["roughening"], "-2.2 12.3 -4.4": ["applaude"], "7.8 22.8 15.8": ["hyphae"], "-4.1 0.2 -1.7": ["textphone"], "8.0 11.2 15.0": ["technic"], "-0.1 17.7 2.1": ["comprehensibly"], "4.0 -0.9 8.6": ["cimbalom"], "13.1 12.3 30.5": ["moorhen"], "14.8 4.7 26.6": ["nicotiana"], "-4.2 2.3 1.0": ["clergywomen"], "0.4 13.4 11.9": ["osu"], "11.8 9.0 9.8": ["stymying"], "1.9 -3.8 6.6": ["winnng"], "-4.0 0.9 12.6": ["stevioside"], "6.4 13.3 9.3": ["belowground"], "1.3 12.4 -3.9": ["continuosly"], "4.2 6.1 15.6": ["feh"], "-1.0 13.1 5.8": ["disinheritance"], "9.6 9.0 18.0": ["giri"], "-2.6 7.6 0.1": ["elvucitabine"], "0.2 15.3 14.2": ["bromantic"], "8.5 2.1 2.1": ["saddlemaker"], "15.7 13.4 15.9": ["ergs"], "4.6 17.1 9.6": ["feebler"], "7.0 -3.4 -7.3": ["opthalmic"], "7.4 9.6 18.1": ["armwrestling"], "5.3 7.9 0.9": ["stabler"], "12.4 6.6 2.7": ["tghe"], "6.9 -0.7 -5.0": ["passim"], "0.3 1.1 10.9": ["cellulase"], "16.4 5.5 12.6": ["decimalisation"], "5.9 10.7 14.0": ["diabase"], "11.2 2.8 9.6": ["slue"], "2.2 14.4 6.7": ["adamancy"], "-2.3 3.7 1.6": ["monitorable"], "11.5 28.3 2.2": ["arrogates"], "-3.2 10.8 8.0": ["longerons"], "6.7 17.6 15.2": ["humdingers"], "3.8 7.1 6.9": ["regionalise"], "11.4 22.1 16.5": ["unevolved"], "8.2 10.7 14.2": ["worrierking"], "6.3 11.2 7.0": ["kdawson"], "11.5 6.6 -4.8": ["aircards"], "5.4 1.6 13.9": ["hfrs"], "-0.0 15.4 13.4": ["pettifogging"], "2.0 8.0 27.9": ["fishkill"], "-2.0 3.4 -3.0": ["trialogue"], "5.2 7.9 18.7": ["uncrushed"], "-6.5 1.2 3.4": ["socred"], "3.8 32.4 4.4": ["reconnoitre"], "-2.2 10.2 11.4": ["durational"], "2.0 2.5 -0.2": ["rund"], "12.1 12.8 40.8": ["shads"], "1.1 7.2 4.2": ["coarctation"], "12.4 13.0 13.9": ["speakin"], "8.8 20.1 22.7": ["corvids"], "1.5 1.5 4.1": ["accapella"], "3.4 10.6 8.2": ["cohered"], "-1.5 -0.4 10.1": ["callover"], "-1.2 6.6 15.2": ["kaha"], "0.9 -1.5 8.2": ["tipsheet"], "4.5 -3.0 8.6": ["streetchildren"], "4.4 8.3 3.3": ["earcup"], "-0.1 -3.6 9.1": ["steen"], "5.6 10.2 14.0": ["ange"], "5.7 13.8 13.6": ["quipster"], "4.0 12.3 6.9": ["raspier"], "-2.4 -3.4 12.3": ["bree"], "6.4 7.2 7.8": ["slokas"], "-0.6 -3.1 9.5": ["reccomendations"], "8.2 19.3 -2.0": ["incapacities"], "3.8 7.5 23.3": ["ubi"], "1.7 11.4 0.7": ["descision"], "3.7 -3.7 9.5": ["wrth"], "6.4 13.8 13.4": ["gir"], "17.0 19.5 4.1": ["frontward"], "-2.7 8.1 10.6": ["passband"], "13.0 15.7 13.8": ["tenderpreneurs"], "5.1 -0.5 5.9": ["fotos"], "9.1 -1.0 9.1": ["calander"], "5.8 20.8 4.9": ["narcissistically"], "7.3 10.0 5.6": ["prius"], "6.5 7.7 12.1": ["prety"], "5.0 0.8 18.0": ["octa"], "1.2 7.6 7.3": ["olecranon"], "-6.8 -3.0 4.5": ["classe"], "1.6 24.4 4.1": ["misspeaks"], "7.4 20.4 15.0": ["bridezillas"], "10.7 0.9 6.7": ["offficials"], "10.1 16.5 29.5": ["insectivores"], "4.6 12.6 -0.4": ["deficiences"], "3.7 10.0 27.3": ["tarsiers"], "-1.1 14.9 8.0": ["teaparty"], "3.7 3.9 6.4": ["bution"], "18.2 12.8 -4.2": ["flacking"], "2.8 2.9 3.5": ["eith"], "7.6 6.4 10.7": ["polys"], "-3.5 14.2 -4.7": ["psychopathological"], "7.8 17.6 18.1": ["backbends"], "1.7 12.8 0.2": ["disrict"], "2.7 22.1 9.4": ["exploitability"], "-3.0 0.1 11.5": ["haats"], "15.9 14.7 28.0": ["foxhound"], "7.3 10.7 10.2": ["electrifyingly", "predominently"], "0.5 5.5 7.9": ["thefacebook"], "17.6 10.5 6.7": ["firelighters"], "11.7 10.8 10.2": ["nanomotor"], "-0.0 0.5 18.5": ["sealcoat"], "7.9 8.9 8.1": ["microcalcifications"], "20.9 10.7 16.9": ["clop"], "20.7 -4.7 4.5": ["babycare"], "6.2 9.4 3.7": ["overperforming"], "26.7 9.1 17.1": ["featherlight"], "5.5 8.9 10.7": ["repecharge"], "5.5 11.1 5.9": ["autostrada"], "16.0 15.0 20.4": ["cornier"], "22.0 26.3 14.6": ["forcefield"], "1.7 22.7 7.0": ["traduce"], "-1.2 -1.7 17.4": ["crossbreds"], "7.9 3.7 3.5": ["rade"], "15.6 5.8 22.1": ["occidentalis"], "5.1 15.1 6.2": ["karega"], "6.0 12.2 1.9": ["differencing"], "14.1 2.7 -5.7": ["revolutionalise"], "-4.6 11.9 15.0": ["busser"], "10.1 26.3 5.5": ["speaketh"], "5.1 15.5 14.3": ["haath"], "-0.9 6.6 14.2": ["iftaar"], "15.1 2.3 33.1": ["rosti"], "4.8 27.4 7.2": ["mobocracy"], "3.2 -0.3 6.5": ["svcs"], "-0.9 23.9 8.1": ["medivaced"], "3.5 13.0 19.1": ["predigested"], "0.4 7.0 13.2": ["hemoptysis"], "9.7 3.3 24.7": ["homecooked"], "-9.4 8.7 10.5": ["reappropriate"], "5.5 0.5 2.2": ["informationabout"], "5.0 16.3 12.8": ["poa"], "3.7 9.1 3.0": ["forwardlooking"], "5.9 0.4 12.9": ["futuro"], "-8.2 5.8 3.9": ["chemoembolization"], "12.1 8.6 14.0": ["superheating"], "13.8 7.3 5.3": ["hellraisers"], "5.9 2.6 1.8": ["transcutaneous"], "25.1 7.0 21.4": ["upsidedown"], "3.5 12.3 11.4": ["anaerobically"], "8.9 5.4 8.0": ["rumbly"], "1.2 5.2 16.1": ["acequia"], "-2.4 11.1 -0.5": ["achivement"], "-0.0 16.4 9.6": ["unction"], "0.6 12.0 13.8": ["hopkins"], "10.3 23.3 10.6": ["geostrategy"], "18.6 12.3 8.2": ["badshah"], "12.4 14.3 17.7": ["paschal"], "20.5 12.2 23.2": ["brewskies"], "3.2 4.2 -1.7": ["proble"], "4.8 9.4 8.3": ["psychoacoustic"], "-5.5 26.1 3.0": ["coupists"], "3.3 -0.2 17.5": ["lissencephaly"], "11.3 -4.0 1.8": ["chairmain"], "7.3 9.4 10.5": ["breathily"], "9.4 8.7 12.6": ["wantin"], "2.6 -3.0 14.9": ["marketbasket"], "8.4 17.3 4.6": ["arond"], "9.8 11.3 4.5": ["econony"], "9.5 9.9 46.6": ["sockeyes"], "7.2 32.9 -4.3": ["footsoldier"], "-1.6 -1.0 4.4": ["clubgolf"], "4.7 3.2 15.1": ["trappy"], "19.0 6.3 10.8": ["speccy"], "0.6 9.0 3.1": ["obatoclax"], "2.4 -3.9 4.3": ["bunionectomy"], "1.6 2.2 7.8": ["carloadings"], "10.6 2.7 1.3": ["trigeneration"], "-0.3 21.5 14.8": ["crudities"], "6.3 12.3 12.4": ["cbscowards"], "11.1 13.1 6.2": ["hyperventilates"], "7.0 10.1 15.5": ["negra"], "16.9 8.0 7.7": ["ungracefully"], "-9.3 6.5 0.6": ["endotoxemia"], "6.5 13.3 9.4": ["pederasts"], "9.1 25.9 1.8": ["harakiri"], "-3.2 5.3 10.0": ["viceregal"], "-0.2 0.4 12.6": ["greta"], "-5.0 0.6 6.2": ["hypnobirthing"], "-5.0 17.7 6.5": ["chambering"], "3.2 20.7 7.8": ["misdials"], "-6.1 -5.5 6.9": ["deverus"], "15.0 16.0 15.0": ["gleeks"], "4.8 18.3 0.7": ["polical"], "11.9 17.9 16.0": ["threequels"], "5.8 15.6 22.1": ["grue"], "-4.8 13.0 19.9": ["snowcover"], "24.6 16.5 22.7": ["serviette"], "10.2 8.5 11.3": ["settin"], "-4.2 1.6 4.6": ["cidofovir"], "2.9 14.5 9.6": ["assest"], "11.5 17.6 6.6": ["instructively"], "5.7 5.9 8.2": ["sopcast"], "-2.6 -1.3 5.2": ["nefazodone"], "17.4 -3.7 -4.9": ["leadingprovider"], "5.3 -2.7 4.3": ["assayer"], "18.2 -1.2 16.0": ["beelined"], "6.9 0.8 7.7": ["processs"], "-1.5 7.6 7.5": ["karna"], "1.9 3.4 13.7": ["corto"], "-1.8 5.1 15.1": ["mihi"], "-0.3 -3.2 5.7": ["cours"], "3.4 7.7 -0.1": ["amont"], "19.1 6.0 17.0": ["serape"], "-2.6 13.0 2.8": ["vagal"], "-2.3 -1.2 27.2": ["verjus"], "-9.1 4.3 2.4": ["radiculopathy"], "-7.5 7.7 4.4": ["prefinal"], "3.8 11.7 7.3": ["parikrama"], "19.2 15.1 23.5": ["splintery"], "19.8 8.3 31.4": ["kebobs"], "13.4 8.7 19.8": ["nian"], "2.6 10.9 12.4": ["beggers"], "-0.9 25.4 1.9": ["palestine"], "8.2 14.7 8.4": ["flusters"], "2.6 7.9 3.0": ["nell"], "-3.0 24.1 -1.2": ["valiance"], "9.6 26.2 1.7": ["precognitive"], "0.4 8.5 2.2": ["doch"], "-0.5 13.6 -5.5": ["webloggers"], "3.1 6.0 4.4": ["medicalised"], "3.1 14.1 6.0": ["sectorally"], "16.0 15.0 25.9": ["woad"], "17.1 13.8 11.8": ["stroboscopic"], "11.1 -8.7 11.7": ["chairbacks"], "-7.4 8.4 6.5": ["amoungst"], "-3.8 7.4 -4.4": ["andhis"], "14.9 -5.7 0.9": ["ompany"], "14.8 17.7 10.1": ["woosh"], "5.3 4.0 -7.2": ["unpleased"], "8.4 15.5 12.1": ["fook"], "7.1 5.4 10.5": ["agenices"], "8.8 28.7 17.5": ["streetfight"], "1.6 25.2 4.9": ["intuiting"], "0.3 12.1 12.3": ["headgate"], "11.4 4.5 17.4": ["corolla"], "10.9 10.8 7.9": ["brattish"], "5.4 6.7 9.6": ["averge"], "5.5 -3.2 25.7": ["defatted"], "4.0 -7.5 11.6": ["msc"], "7.3 18.6 16.4": ["lowlanders"], "1.6 14.1 2.0": ["arbitary"], "-5.3 13.1 8.1": ["geochemically"], "0.8 15.0 8.2": ["similiarities"], "3.6 1.0 1.4": ["dzine"], "5.2 6.0 18.9": ["zheng"], "-5.1 2.5 7.9": ["waivable"], "14.5 29.2 9.2": ["apparat"], "1.6 1.0 3.6": ["bfa"], "6.0 14.5 10.5": ["featurephone"], "-0.6 6.9 6.2": ["chalkings"], "3.5 1.6 -8.3": ["isin"], "10.1 13.2 11.0": ["fisticuff"], "16.1 17.1 21.9": ["bonks"], "13.9 9.2 7.6": ["prepack"], "-2.1 6.2 4.4": ["sigmoidoscopies"], "19.7 6.6 40.0": ["brochettes"], "13.1 15.8 10.7": ["spector", "namaskar"], "7.8 5.5 23.6": ["salo"], "3.0 9.5 2.2": ["artiklile"], "-3.6 -1.4 22.0": ["manis"], "4.0 2.2 6.7": ["antispasmodic"], "-2.8 17.1 6.9": ["nepal"], "1.9 4.2 9.5": ["implementor"], "-11.5 -5.6 -1.6": ["enroled"], "-3.8 15.7 8.5": ["perfectionistic"], "-2.7 4.9 0.4": ["accu"], "-0.7 11.6 4.8": ["sulcus"], "0.3 8.4 13.6": ["totoo"], "7.7 24.1 8.8": ["insolvable"], "-3.8 3.4 6.9": ["scorless"], "17.7 4.5 21.7": ["chugger"], "-8.1 8.7 6.6": ["nonserious"], "1.0 13.2 9.7": ["liposarcoma"], "34.1 13.8 9.0": ["conglomerated"], "18.9 17.4 3.3": ["hazzard"], "4.3 6.5 17.2": ["scruffiness"], "15.5 13.6 9.1": ["homogenising"], "4.9 -0.1 8.5": ["microparticle"], "10.6 10.6 12.2": ["gads"], "-2.2 11.0 7.5": ["cytokinesis"], "-4.2 36.9 3.2": ["counterinsurgents"], "7.1 0.9 13.0": ["terpene"], "8.3 5.2 14.8": ["nosegay"], "2.0 2.9 8.4": ["ecomomic"], "7.3 14.0 4.4": ["perceptional"], "10.4 2.8 26.6": ["tablespoonfuls"], "5.6 7.0 -0.3": ["taggants"], "-1.7 2.3 -1.9": ["triazolam"], "5.9 3.7 5.5": ["mesylate"], "14.2 0.3 17.8": ["rico"], "-2.7 13.5 4.2": ["nakabandi"], "8.3 11.1 3.9": ["indiscrete"], "13.4 16.5 7.3": ["globalizes"], "6.3 5.6 11.3": ["waterpipes"], "1.7 4.9 12.1": ["peng"], "2.0 -6.6 2.6": ["eigh"], "8.7 -7.9 4.2": ["withan"], "-4.2 17.2 7.8": ["rereads"], "7.7 14.7 19.0": ["riversides"], "-6.8 13.3 5.6": ["placee"], "-5.9 8.7 3.8": ["pseudoaneurysm"], "7.0 15.7 -5.5": ["coaliton"], "6.6 11.8 13.9": ["nosepiece"], "10.1 2.3 14.3": ["noice"], "7.0 10.5 10.2": ["tectonically"], "9.2 10.9 31.0": ["borsch"], "2.3 12.0 8.2": ["kalam"], "6.5 13.3 8.7": ["frissons"], "9.8 6.2 18.4": ["waa"], "-6.1 13.7 0.2": ["disavowals"], "11.7 3.1 18.5": ["nibblies"], "7.6 7.4 13.7": ["grumbly"], "9.7 22.3 18.2": ["kickbox"], "16.8 9.4 9.9": ["kajillion"], "3.9 -6.1 6.5": ["ete"], "-1.9 -2.8 4.3": ["sociale"], "-0.3 5.8 -0.4": ["dexmedetomidine"], "-3.5 5.6 4.2": ["gyrus"], "6.0 5.3 4.6": ["dann"], "20.3 10.4 9.9": ["evrything"], "-5.6 10.1 4.7": ["riyaaz"], "-0.3 8.8 14.5": ["kookier"], "12.1 -2.6 6.4": ["riche"], "4.2 1.3 1.8": ["contr"], "-6.1 11.2 0.3": ["amikacin"], "18.3 10.7 32.0": ["roseate"], "3.7 16.0 14.1": ["politians"], "28.1 22.5 19.6": ["unobtanium"], "10.7 29.9 14.5": ["squealer"], "8.9 5.0 4.5": ["spaceframe"], "-2.3 3.8 7.1": ["teleserial"], "13.2 24.9 29.9": ["webworms"], "3.4 6.7 8.3": ["amiloride"], "19.4 24.3 16.9": ["forboding"], "-2.4 5.4 6.6": ["prepone"], "4.2 9.7 5.6": ["celebrityhood"], "10.7 8.2 38.6": ["demiglace"], "-1.9 12.7 2.4": ["discountenanced"], "5.5 10.3 5.0": ["upshots"], "12.9 16.5 29.3": ["bimini"], "21.1 10.1 -0.6": ["mobilcom"], "10.3 0.8 2.0": ["capcity"], "-2.7 11.0 8.0": ["equilibria"], "0.1 0.5 7.9": ["mdash"], "-2.9 8.3 14.7": ["explications"], "-5.0 5.3 -1.2": ["afatinib"], "0.4 0.7 13.7": ["collegiates"], "5.4 4.7 -0.1": ["reimport"], "0.8 1.3 17.5": ["campylobacteriosis"], "0.2 16.4 3.9": ["coextensive"], "1.9 7.4 11.9": ["okey"], "6.0 8.2 3.9": ["seit"], "7.6 16.3 -1.9": ["mainsteam"], "18.3 17.1 23.5": ["lawnchair"], "16.7 24.4 14.3": ["reanimates"], "0.3 8.2 -2.1": ["netomat"], "9.4 14.0 11.1": ["leanly"], "-2.2 3.7 6.4": ["safai"], "6.4 14.7 6.9": ["catalytically"], "13.3 15.9 17.4": ["fatuity"], "12.3 16.0 8.8": ["churlishly"], "18.4 2.7 3.3": ["unwieldly"], "5.4 3.6 8.2": ["ceasework"], "13.0 20.3 25.6": ["foxtails"], "0.5 12.6 8.4": ["zis"], "9.9 -8.2 5.0": ["recherche"], "12.0 12.7 15.6": ["trackpoint"], "6.7 8.6 15.8": ["fanciness"], "0.8 12.3 7.9": ["reciters"], "16.2 6.4 22.6": ["rooty"], "0.3 13.6 15.8": ["hamari"], "6.5 1.4 2.7": ["dgm"], "1.0 6.3 18.4": ["techni"], "14.7 10.3 16.4": ["drably"], "16.6 4.8 11.5": ["lissom"], "0.5 0.8 -2.4": ["disapperance"], "19.0 11.9 30.0": ["arum"], "-1.4 15.7 -2.2": ["liasons"], "5.2 10.9 7.5": ["rohypnol"], "4.8 6.0 2.3": ["biometry"], "-5.1 19.4 5.4": ["relgious"], "9.0 11.1 10.0": ["dugg"], "1.3 2.8 7.3": ["placemaking"], "-6.6 14.1 0.8": ["handwritings"], "5.7 15.6 15.4": ["asexuals"], "-3.1 19.2 11.5": ["indissolubility"], "-4.4 8.2 3.4": ["remediations"], "3.9 26.6 9.6": ["demine"], "5.8 -5.7 8.2": ["earier"], "-1.3 3.0 -2.1": ["tarmacking"], "5.7 19.2 8.3": ["tragedian"], "-1.0 9.6 12.9": ["bicam"], "2.8 3.5 10.9": ["decumulation"], "11.9 -1.7 16.8": ["squawky"], "14.5 24.4 8.5": ["placeless"], "0.2 13.7 2.6": ["loopier"], "-0.3 7.7 22.3": ["eyespot"], "12.9 23.3 26.7": ["mattock"], "23.3 10.7 -2.0": ["devision"], "4.1 -1.0 6.1": ["dialyzers"], "-1.5 1.0 1.7": ["ias"], "3.8 13.2 27.3": ["keema"], "4.1 18.7 9.3": ["ouf"], "0.6 2.6 8.3": ["transmucosal"], "12.7 23.3 9.8": ["crump"], "8.2 9.0 20.6": ["leguminous"], "9.5 12.8 14.5": ["baap"], "8.0 9.8 7.7": ["spottily"], "6.3 0.8 14.6": ["componentization"], "13.2 12.4 8.4": ["caustics"], "8.5 8.4 17.6": ["rakugo"], "-6.3 -0.2 -1.8": ["fpa"], "11.4 32.7 24.5": ["pvp"], "6.2 29.0 38.3": ["greenheads"], "10.0 -4.7 2.4": ["miilion"], "-7.4 18.2 -4.2": ["formost"], "0.6 6.4 7.5": ["glutamatergic"], "3.4 7.6 32.9": ["sassathon"], "19.8 18.8 21.2": ["pipsqueaks"], "-0.8 16.6 -0.5": ["reconcilliation"], "2.7 -2.2 -3.2": ["licensers"], "13.1 7.3 10.0": ["forza"], "-3.7 12.4 1.7": ["movants"], "8.5 1.9 9.1": ["kahn"], "4.2 6.2 8.0": ["quasicrystals"], "11.6 6.2 7.8": ["kunnen"], "3.1 36.4 15.0": ["duelist"], "-8.7 6.0 15.9": ["maf"], "-0.4 1.5 4.5": ["basketbal"], "7.9 3.8 17.3": ["spumante"], "-2.6 17.2 -1.8": ["ambits"], "-7.4 11.2 5.8": ["discouragements"], "18.1 15.0 9.4": ["unaesthetic"], "18.7 9.2 24.6": ["stalky"], "16.9 8.1 15.2": ["freddie"], "10.0 3.9 21.6": ["chinensis"], "7.5 11.5 -3.1": ["metaio"], "-8.6 13.5 8.2": ["abstainer"], "1.4 16.8 10.6": ["thermodynamically"], "-6.8 18.2 6.3": ["differant"], "11.7 1.6 15.5": ["pricer"], "17.4 6.1 11.1": ["carbonised"], "-3.6 9.2 3.1": ["woking"], "-0.2 -6.1 0.6": ["prinicpal"], "7.6 1.5 14.4": ["headcovers"], "9.8 20.6 17.5": ["lunk"], "0.6 28.5 6.6": ["paleoconservatives"], "17.6 20.7 5.9": ["impregnability"], "2.4 13.0 6.2": ["sluttish"], "-1.4 12.3 7.1": ["staginess", "robocalling"], "13.0 18.2 8.1": ["danda"], "6.8 17.1 0.4": ["refire"], "5.4 7.8 14.7": ["paa"], "12.7 14.4 4.1": ["hearthstone"], "16.6 14.3 22.3": ["greasiest"], "-4.2 24.4 7.2": ["tazers"], "3.8 21.5 5.5": ["absoluteness"], "16.7 5.4 24.8": ["palo"], "4.6 17.1 17.1": ["dominoed"], "-3.5 2.9 7.4": ["lein"], "1.5 1.5 1.5": ["recoverables"], "4.9 9.6 5.6": ["dic"], "11.9 4.1 9.4": ["scammy"], "-0.2 0.2 5.1": ["rebaudioside"], "-4.3 13.8 9.3": ["discription"], "3.0 6.9 16.7": ["unfamous"], "11.1 13.8 20.4": ["meadowlands"], "-2.8 17.6 0.9": ["disinterestedness"], "26.5 18.6 15.0": ["whump"], "4.3 9.0 10.3": ["definatley"], "5.5 14.9 9.3": ["blogospheric"], "2.3 11.6 7.4": ["namedropping"], "1.8 1.8 6.5": ["eeks"], "6.5 6.7 5.7": ["vraiment"], "1.2 7.2 7.9": ["woodshedding"], "5.0 13.1 6.0": ["biocapacity"], "17.5 10.0 12.1": ["porny"], "-3.9 -3.1 2.8": ["valent"], "1.9 6.1 6.7": ["nonscheduled"], "20.2 10.9 18.8": ["semicircles"], "8.2 7.1 19.8": ["holidayers"], "19.7 4.7 10.3": ["infrastruture"], "14.4 11.1 22.9": ["waterer"], "-1.9 6.9 17.3": ["riverway"], "11.0 4.6 42.0": ["caviars"], "8.8 32.8 1.0": ["anticolonial"], "5.3 17.0 -9.4": ["condemed"], "20.8 5.8 7.8": ["totin"], "3.4 3.0 6.3": ["rheometer"], "16.3 5.8 14.2": ["rustproof"], "-4.8 21.6 17.9": ["kinfolks"], "13.3 11.0 14.0": ["argentine"], "6.8 1.9 11.6": ["morgage"], "-4.7 3.0 4.5": ["collectorates"], "9.0 7.7 6.4": ["phot"], "7.6 9.2 12.4": ["doldrum"], "3.8 9.0 3.1": ["bodychecked"], "8.7 3.2 -2.0": ["thepublic"], "0.6 -1.1 6.7": ["emergn"], "-6.3 0.9 2.0": ["dikir"], "-2.8 8.7 5.1": ["schoool"], "14.9 12.9 26.5": ["rhea"], "-1.0 24.1 2.5": ["persuit"], "-5.5 6.6 8.8": ["microcoils"], "5.3 6.2 15.0": ["wineskins"], "14.1 4.7 17.5": ["wimple"], "13.2 1.7 -7.2": ["codevelop"], "0.0 4.1 2.5": ["dignataries"], "5.1 12.0 36.0": ["gaminess"], "-1.1 5.6 6.7": ["ticlopidine"], "-4.0 5.4 4.5": ["precisions"], "11.8 12.7 18.0": ["arf"], "7.6 -1.8 -3.6": ["coproduce"], "9.4 15.3 6.3": ["tattler"], "6.7 2.3 11.8": ["usc"], "5.0 12.7 2.9": ["comex"], "8.8 8.9 6.3": ["interphase"], "3.1 -8.9 11.1": ["tlc"], "14.4 -0.7 -0.7": ["vividwireless"], "12.8 8.7 14.9": ["plie"], "11.5 18.8 10.5": ["strikepower"], "18.8 4.8 7.4": ["makarapa"], "4.5 9.8 0.8": ["sucha"], "9.2 -9.3 7.4": ["exibition"], "2.9 3.3 4.3": ["tiwi"], "3.3 38.8 11.2": ["mortaring"], "0.9 4.4 2.1": ["amendement"], "1.6 16.9 -0.8": ["impracticalities"], "5.7 18.9 16.6": ["ludic"], "17.0 5.7 30.5": ["unstuffed"], "9.9 10.7 11.2": ["dod"], "10.6 21.3 17.0": ["knobkerrie"], "16.3 7.4 4.8": ["moonshots"], "7.6 9.3 12.4": ["arthur", "crys"], "6.9 18.0 8.0": ["gimps"], "-0.6 10.9 7.4": ["priveleges"], "6.4 8.2 13.5": ["bazars"], "5.9 21.5 14.2": ["purposelessness"], "7.5 12.4 17.6": ["nondigital"], "20.4 16.1 14.1": ["fieriest"], "9.1 4.5 7.8": ["yog"], "8.7 23.1 4.2": ["aicraft"], "4.2 -1.0 10.0": ["lacoste"], "8.3 7.6 6.3": ["fasion"], "6.8 1.2 5.7": ["severence"], "-7.2 -1.1 3.7": ["methodone"], "4.7 1.5 5.4": ["reformate"], "5.8 -2.3 10.8": ["hyn"], "7.2 -4.0 4.2": ["programma"], "0.3 8.5 14.5": ["chipleader"], "-5.3 7.7 5.7": ["neurotrophic"], "6.1 -3.0 0.5": ["headling"], "4.4 4.4 17.8": ["catherine"], "-1.7 4.1 8.5": ["lutetium"], "-5.2 3.6 5.1": ["deserializer"], "22.6 11.2 17.0": ["bermed"], "-4.5 3.0 3.8": ["refarming"], "7.8 8.8 7.4": ["resuscitator"], "23.0 19.3 15.2": ["clockworks"], "3.5 16.4 2.4": ["violaters"], "13.2 2.4 8.7": ["tracksuited"], "2.6 15.1 6.7": ["deifies"], "-0.3 4.0 18.1": ["taong"], "12.7 4.1 5.2": ["removalists"], "5.6 15.2 8.5": ["epiphanic"], "17.2 13.0 13.2": ["rattly"], "11.5 12.4 12.3": ["bladdered"], "9.2 1.0 42.2": ["poussin"], "2.9 14.6 23.4": ["chilblains"], "12.1 15.7 4.8": ["backhandedly"], "3.2 0.8 10.9": ["halftones"], "12.8 1.4 16.5": ["gargles"], "11.1 9.5 13.6": ["postcoital"], "16.4 2.2 28.8": ["seafoam"], "6.9 0.9 6.0": ["foi"], "12.0 14.5 0.3": ["interlinks"], "-2.4 0.8 4.7": ["seop"], "9.0 11.0 23.2": ["pana"], "8.1 20.1 17.9": ["doosras"], "9.8 14.1 18.7": ["drear"], "8.2 -5.5 3.2": ["surgey"], "10.9 13.2 7.7": ["hahahah"], "17.7 4.2 12.7": ["abig"], "11.2 20.9 17.7": ["ironclads"], "2.1 9.6 6.9": ["upskirting"], "11.7 12.1 20.1": ["discolouring"], "7.6 2.2 14.1": ["piked"], "14.6 18.6 7.1": ["uncrackable"], "3.2 6.1 2.6": ["multistandard"], "-2.0 22.7 5.5": ["misandry"], "7.8 3.9 13.6": ["stuttery"], "13.8 4.9 13.1": ["trophys"], "2.8 2.2 15.8": ["iyang"], "7.1 11.2 22.4": ["unneutered"], "18.4 8.9 25.7": ["sharky"], "11.1 14.8 10.3": ["adorers"], "5.5 19.6 18.7": ["overexcitement"], "7.8 4.4 9.8": ["builts"], "9.9 5.0 2.0": ["megatrade"], "4.5 7.0 7.8": ["tempoed"], "0.7 5.9 3.4": ["exellent"], "12.0 0.8 6.1": ["tradings"], "8.7 12.4 13.9": ["backwoodsmen"], "15.4 3.2 16.1": ["barony"], "-1.6 -0.1 3.7": ["nated"], "13.6 11.4 12.8": ["stagefright"], "10.9 12.8 1.6": ["mistakingly"], "0.4 23.2 9.7": ["satphone"], "16.9 10.6 25.5": ["chasin"], "8.2 8.0 45.8": ["pipi"], "9.3 19.2 2.2": ["pivotally"], "14.5 12.1 27.8": ["goldenrods"], "-5.5 12.9 4.0": ["opionion"], "9.7 18.8 1.1": ["destoyed"], "13.8 17.5 8.7": ["sics"], "15.8 31.1 12.7": ["freebooters"], "5.7 10.5 14.5": ["glutens"], "7.8 12.7 8.4": ["naija"], "-1.5 20.8 1.3": ["subedar"], "11.7 14.4 30.3": ["centerboard"], "14.3 16.5 7.8": ["debauching"], "6.9 12.6 9.2": ["bengals"], "3.5 14.5 9.4": ["rahul"], "-1.7 -4.9 0.8": ["voc"], "6.6 27.2 11.5": ["libtards"], "7.5 18.3 4.8": ["propinquity"], "16.4 17.4 6.5": ["slipperiest"], "-0.3 5.8 19.2": ["flosses"], "4.0 13.6 4.9": ["diagramed"], "5.8 9.7 -8.6": ["pivitol"], "2.1 8.8 8.9": ["uga"], "-12.0 15.4 5.3": ["articulable"], "0.5 13.3 9.2": ["exept"], "11.2 1.5 2.4": ["visualiser"], "7.9 2.7 17.0": ["sulphite"], "22.2 23.1 43.3": ["finny"], "3.5 8.5 5.4": ["apprehensiveness"], "5.6 12.5 21.8": ["portulaca"], "13.2 -1.7 6.8": ["hairsprays"], "4.1 9.4 8.0": ["coeval"], "14.6 8.0 5.6": ["tyhe"], "2.8 1.2 6.1": ["synthesises"], "5.8 2.8 8.9": ["clubheads"], "-0.4 0.5 -0.6": ["concering"], "-1.5 3.4 10.4": ["hypercholesterolaemia"], "-2.4 5.0 0.9": ["enstoolment"], "13.4 18.1 18.3": ["slippin"], "11.6 23.3 18.6": ["wearies"], "8.9 -4.1 15.5": ["frae"], "17.2 9.4 31.0": ["pandanus"], "8.8 16.3 9.4": ["thanklessly"], "-2.3 4.0 23.4": ["unspayed"], "-2.1 11.2 7.7": ["kapoor"], "16.2 11.0 22.7": ["scentless"], "2.2 -2.0 0.6": ["willhave"], "-0.8 15.5 16.4": ["northeasterners"], "-7.0 3.4 3.6": ["underassessed"], "14.9 12.9 52.3": ["mudfish"], "13.4 7.2 6.4": ["remoulding"], "-8.1 6.2 -3.1": ["affi"], "-3.7 9.8 0.5": ["constitutency"], "16.9 4.1 11.1": ["roundels"], "5.2 0.5 2.9": ["aspart"], "5.6 13.8 20.6": ["wormers"], "15.5 3.6 35.3": ["yakisoba"], "-0.6 6.2 5.5": ["remonstrators"], "17.1 -8.8 8.4": ["neutraceutical"], "-4.0 7.9 3.7": ["immunostimulatory"], "15.5 -3.8 10.2": ["paintshop"], "9.0 29.3 8.4": ["osama"], "3.7 -5.3 12.6": ["quetzales"], "1.5 4.7 19.1": ["khon"], "19.3 7.9 7.2": ["mimicks"], "3.8 -5.8 9.7": ["rhwng"], "6.2 24.7 2.3": ["veiw"], "15.2 25.5 12.4": ["slimeballs"], "6.0 27.8 10.4": ["privacies"], "-0.4 12.5 -3.2": ["reboxetine"], "19.8 7.4 16.5": ["jingly"], "4.2 7.7 1.7": ["rallye"], "6.3 21.9 5.9": ["hypocrit"], "24.9 11.4 36.0": ["frogfish"], "4.7 -5.2 16.8": ["tuckshops"], "-2.3 5.2 11.6": ["cholinesterase"], "-8.5 5.0 -3.3": ["reconcilement"], "-1.6 9.5 8.9": ["jathas"], "2.8 4.0 4.7": ["tibbr"], "12.5 2.5 10.6": ["festgoers"], "4.6 -2.8 10.4": ["weeekend"], "-14.2 17.1 -4.6": ["incriminatory"], "-4.6 11.4 3.2": ["typicality"], "-0.7 16.1 -7.1": ["inures"], "8.4 10.1 11.4": ["cryptochrome"], "10.7 7.6 6.2": ["richocheted"], "-2.2 5.9 7.3": ["nonlicensed"], "6.1 8.0 14.7": ["photospread"], "10.5 8.1 13.0": ["knotholes"], "14.8 1.4 30.0": ["pelmeni"], "4.0 -8.1 0.5": ["vicechairman"], "4.8 5.7 15.2": ["urethras"], "12.2 -0.6 11.1": ["muscial"], "-6.0 4.3 7.2": ["rangatahi"], "-3.3 9.0 6.6": ["prospectives"], "6.3 3.7 16.3": ["hillslope"], "3.9 14.8 6.6": ["roadworkers"], "3.1 -0.8 10.5": ["sparer"], "12.9 13.8 6.9": ["murderball"], "14.8 7.7 21.9": ["jillions"], "1.4 15.6 3.4": ["theregion"], "9.1 6.8 8.1": ["tournement"], "6.8 12.1 2.7": ["insitution"], "3.5 6.8 6.7": ["guyz"], "-0.7 -1.7 19.8": ["unaged"], "6.9 25.0 15.0": ["frangible"], "15.8 15.3 23.7": ["raker"], "5.3 9.0 0.2": ["airframers"], "3.8 14.3 14.8": ["skunking"], "16.5 1.7 1.1": ["advertize"], "5.8 13.3 14.9": ["solarization"], "4.0 5.5 8.2": ["coram"], "-2.1 5.3 15.8": ["yaa"], "17.7 13.9 11.2": ["dappling"], "13.6 11.6 12.2": ["fucose"], "10.0 0.7 10.6": ["lub"], "-2.8 5.1 16.2": ["niyan"], "5.4 10.4 8.7": ["underweights"], "0.1 12.3 0.4": ["gandhi"], "28.1 17.0 13.3": ["silhouetting"], "4.9 1.6 7.3": ["ihrer"], "9.9 12.2 7.1": ["lawgivers"], "-4.4 0.7 -4.1": ["reporte"], "9.4 1.5 15.8": ["macchiatos"], "9.0 10.1 24.0": ["shaggers"], "6.9 7.4 12.9": ["formant"], "9.6 18.6 11.7": ["inharmonious"], "-3.9 3.6 1.7": ["monodrama"], "18.0 26.6 17.5": ["elvish"], "9.4 4.0 -2.1": ["greated"], "8.9 5.6 -0.1": ["outift"], "11.1 3.9 15.9": ["cryogen"], "6.5 -1.4 14.7": ["angela"], "-4.6 3.4 11.4": ["avocational"], "-0.1 6.0 7.3": ["mila"], "4.6 15.5 14.2": ["metafictional"], "4.4 6.9 3.1": ["ayer"], "-0.5 -2.7 4.2": ["toincrease"], "12.5 23.6 10.5": ["jackers"], "7.5 19.9 10.5": ["unneighborly"], "-3.5 2.5 23.1": ["reposado"], "-0.4 28.4 6.5": ["prevaricator"], "19.5 14.4 21.8": ["spangle"], "1.7 7.6 21.3": ["ganga"], "18.8 18.3 26.0": ["dingos"], "7.5 8.6 11.5": ["localites"], "19.1 7.9 23.7": ["overlarge"], "-2.2 6.3 6.3": ["fexofenadine"], "2.6 9.6 7.3": ["panyard"], "15.3 7.1 6.6": ["kegerator"], "2.5 10.2 8.3": ["increas"], "18.7 6.2 30.5": ["lisianthus"], "7.7 8.1 10.8": ["eightieth"], "2.5 -3.1 1.0": ["follwoing"], "3.2 18.0 9.9": ["inexpressibly"], "18.8 5.9 19.9": ["barrelful"], "11.8 8.0 17.9": ["winkled"], "10.3 15.5 11.4": ["mooks"], "-0.6 15.6 4.6": ["oing"], "-1.1 -0.8 2.7": ["streetscene"], "9.0 4.1 17.8": ["exhuberant"], "11.3 20.7 21.4": ["leggers"], "11.5 -2.3 0.6": ["popularizes"], "3.4 12.6 9.5": ["redialed"], "8.4 -3.2 11.7": ["subminiature"], "8.6 6.6 33.3": ["mung"], "-7.1 4.5 9.3": ["visibilty"], "3.1 15.5 7.0": ["catenin"], "5.5 15.2 5.4": ["perjurers"], "-0.5 11.1 13.2": ["subfamilies"], "-2.7 0.6 -7.3": ["twotime"], "24.4 13.8 7.7": ["lightspeed"], "6.1 10.7 0.1": ["nonvisual"], "15.3 6.4 15.2": ["closetful"], "15.5 32.0 5.7": ["puppetmasters"], "6.5 1.1 5.7": ["corpora"], "2.0 12.4 4.0": ["antiferromagnetic"], "4.0 6.0 10.4": ["betfair"], "0.2 5.8 23.9": ["muri"], "4.7 12.3 7.5": ["chromitite"], "13.6 10.1 18.7": ["crea"], "9.0 7.0 10.4": ["tearjerking"], "-1.0 11.5 13.4": ["waan"], "9.0 24.8 3.8": ["tradegy"], "1.5 7.2 4.3": ["intensiveness"], "9.5 10.0 12.7": ["mashable"], "7.0 -6.5 9.7": ["hales"], "8.3 8.4 19.7": ["quaffer"], "13.1 7.8 24.9": ["mealie"], "14.9 8.1 12.3": ["swingsets"], "9.8 18.6 6.4": ["conceed"], "7.5 26.6 0.1": ["besieges"], "9.5 10.5 5.0": ["thefinal"], "11.7 10.8 10.1": ["flibbertigibbet"], "4.3 12.4 11.1": ["rani"], "3.2 1.3 0.2": ["aniversary"], "3.6 9.8 8.9": ["pacier"], "12.0 10.9 7.7": ["refaced"], "10.6 17.2 14.6": ["ideograms"], "-9.3 8.5 -3.3": ["disqualifiers"], "8.7 11.9 3.2": ["capologist"], "-1.5 17.9 2.4": ["expositor"], "11.4 14.5 18.7": ["etymologies"], "3.9 10.0 4.5": ["endusers"], "-1.8 17.1 15.0": ["longeron"], "1.3 13.5 11.9": ["diversifiers"], "1.6 19.2 13.2": ["verry"], "-2.5 11.8 -4.4": ["expell"], "6.2 2.1 15.1": ["crewneck"], "11.3 10.3 12.5": ["superhydrophobic"], "-2.8 6.4 11.3": ["pallavi"], "17.7 4.9 17.9": ["drwr"], "4.9 5.0 14.2": ["goodtime"], "9.0 15.0 23.5": ["verbenas"], "13.3 8.3 8.8": ["stultify"], "6.2 11.8 14.0": ["wiccan"], "-0.1 10.1 -8.6": ["withour"], "14.0 9.8 5.9": ["anonymise"], "11.6 9.5 12.5": ["garrets"], "-0.1 1.4 4.6": ["onn"], "-3.8 0.2 5.0": ["booklist"], "1.8 18.2 4.5": ["guardedness"], "9.7 13.3 12.6": ["ablity"], "-3.7 25.5 2.2": ["particularism"], "-5.6 9.7 8.6": ["holeshots"], "10.9 14.4 11.1": ["ladyship"], "17.5 9.0 21.9": ["whiffy"], "4.7 9.9 17.1": ["papilloma"], "11.0 6.4 12.5": ["venturers"], "11.3 23.7 19.6": ["katanas"], "-2.4 15.2 16.5": ["dropball"], "2.5 17.1 8.3": ["sugarcoats"], "7.6 10.8 16.6": ["fishfinders"], "-3.5 11.9 8.6": ["candidemia"], "18.7 11.6 40.1": ["pteropods"], "8.5 8.0 5.2": ["aufgenommen"], "3.0 9.6 14.7": ["bahar"], "-0.9 7.3 6.7": ["atraumatic"], "10.4 26.6 4.2": ["embroilment"], "12.3 11.4 19.5": ["guo"], "-11.1 4.5 4.9": ["nondepressed"], "1.0 15.7 4.4": ["dateable"], "9.3 12.6 10.6": ["fungoes"], "9.8 8.0 17.8": ["lamellae"], "-8.6 -2.2 3.9": ["nonphysician"], "10.7 2.1 24.8": ["bellinis"], "0.6 15.8 17.1": ["lifeways"], "2.1 17.5 11.5": ["jokiness"], "14.3 3.1 46.3": ["matsutake"], "5.7 -2.5 3.7": ["neuropharmacology"], "9.6 10.7 12.5": ["serifs"], "4.3 18.2 2.3": ["flexbone"], "10.4 13.8 4.3": ["crystalizing"], "5.9 29.9 3.9": ["ungodliness"], "2.5 -1.5 12.0": ["triacylglycerol"], "17.8 22.2 8.3": ["hyperreal"], "4.6 19.9 2.3": ["misgoverned"], "6.6 30.2 5.2": ["battlegroups"], "13.9 14.9 13.0": ["confraternity"], "5.5 9.5 15.5": ["goood"], "9.6 18.5 12.9": ["ephemerality"], "1.9 6.1 13.1": ["commissaires"], "10.2 20.2 30.0": ["henbit"], "-4.7 6.1 8.8": ["erythropoiesis"], "7.1 7.1 15.9": ["transpo"], "-2.0 -1.5 3.9": ["questionaires"], "28.4 11.3 28.6": ["squiggling"], "-9.6 9.1 3.6": ["includible"], "0.3 10.6 9.8": ["canot"], "8.7 26.6 3.4": ["disorganise"], "14.2 26.6 4.9": ["mythmakers"], "11.2 5.9 1.3": ["continueto"], "13.9 12.2 5.3": ["couldbe"], "1.7 -6.1 0.7": ["urodynamics"], "16.9 -6.6 27.9": ["frenched"], "5.7 21.2 6.5": ["akward"], "-2.0 33.1 12.9": ["bushwhackers"], "9.7 27.0 5.8": ["unhidden"], "9.2 12.1 5.2": ["rescaled"], "-1.3 8.1 -3.6": ["neuroradiologists"], "-0.3 4.8 16.4": ["agi"], "0.5 -5.3 9.8": ["lignan"], "4.7 9.3 9.3": ["loking"], "-0.3 2.1 0.1": ["sublimit"], "2.5 7.9 9.4": ["amours"], "13.7 9.5 12.6": ["yodeled"], "-9.4 3.2 6.8": ["reoperations"], "-7.7 -0.1 4.3": ["eligble"], "-4.0 12.0 8.5": ["enjoyability"], "-0.9 6.4 5.6": ["noninferior"], "-0.2 12.8 8.5": ["cognoscente"], "4.3 12.5 9.6": ["ronaldinho"], "10.2 10.0 10.0": ["firang"], "-4.0 7.0 12.1": ["malalignment"], "-1.4 5.1 11.5": ["libro"], "28.1 27.4 27.6": ["chocobo"], "13.5 12.5 19.9": ["fram"], "13.6 14.5 1.3": ["capabilties"], "-3.0 2.8 2.6": ["tricyclic"], "17.4 29.4 15.2": ["uzi"], "1.8 2.5 14.7": ["underfeeding"], "-10.6 10.3 1.6": ["uptill"], "6.2 20.2 15.2": ["bunkerers"], "9.5 12.2 13.0": ["wankery"], "6.4 8.6 8.9": ["theeconomy"], "-0.1 11.8 8.9": ["dancier"], "-4.9 -1.2 11.0": ["nonrelated"], "9.8 3.7 10.7": ["nutriceuticals"], "4.5 14.6 2.6": ["analogizing"], "0.2 14.2 6.7": ["blackmoney"], "-4.7 20.9 10.7": ["adulticide"], "6.3 21.1 10.6": ["incandescently"], "5.2 -0.7 16.5": ["bullions"], "12.7 7.0 12.4": ["agrofuel"], "5.4 10.1 1.3": ["paginated"], "16.2 6.0 11.9": ["bmx"], "0.6 3.6 4.3": ["gatifloxacin"], "7.4 23.1 16.2": ["selfs"], "10.4 13.6 9.5": ["conn"], "-2.6 6.1 4.8": ["tendinopathy"], "1.3 8.4 7.1": ["sheva"], "-5.4 5.8 9.0": ["precancer"], "-2.0 5.0 -5.5": ["thenumber"], "11.7 -5.4 7.6": ["projet"], "7.6 6.9 30.1": ["naans"], "8.0 5.8 0.5": ["finagles"], "12.4 5.3 10.9": ["folktronica"], "4.3 7.5 14.2": ["palatal"], "-0.1 4.2 11.5": ["kippot"], "3.0 13.4 16.0": ["transhipped"], "10.0 19.2 9.9": ["fixedly"], "9.8 4.2 11.2": ["fortyish"], "2.5 7.8 2.2": ["manuel"], "1.2 34.1 6.1": ["bombardiers"], "2.7 12.5 12.3": ["epilepsies"], "3.9 6.1 1.5": ["webstream"], "21.8 13.5 22.2": ["snakey"], "5.2 24.8 10.5": ["cravenness"], "-1.9 9.2 5.8": ["burlesques"], "18.6 16.2 35.9": ["antarctic"], "-6.8 10.7 12.1": ["seminoma"], "12.9 20.3 15.1": ["chinny"], "12.3 2.8 13.3": ["coachmen"], "2.8 13.0 14.7": ["tue"], "4.1 6.7 7.0": ["ijara"], "10.1 5.4 -2.8": ["serach"], "6.1 7.3 9.9": ["jaise"], "9.8 1.6 21.3": ["unconsumed"], "-0.2 7.1 15.7": ["kola"], "1.6 11.4 10.4": ["subtotals"], "12.5 12.2 19.4": ["bootlace"], "-4.2 6.4 4.1": ["kebele"], "3.6 18.7 16.4": ["pitchouts"], "10.4 -0.3 19.1": ["terrasse"], "11.5 31.2 11.1": ["lowliness"], "0.8 8.6 25.1": ["hanami"], "-1.0 7.9 5.4": ["jaywalked"], "-3.9 -4.5 9.7": ["amat"], "2.7 27.0 6.8": ["boers"], "-3.7 -1.0 2.4": ["hysteroscopy"], "0.8 -4.4 -0.0": ["etown"], "13.9 10.8 14.4": ["gamin"], "9.7 15.2 14.4": ["howlingly"], "9.9 0.7 19.4": ["tyme"], "3.8 8.9 10.4": ["revit"], "11.9 11.4 18.8": ["lindens"], "13.7 7.0 17.3": ["pukey"], "8.9 6.2 8.8": ["semitrucks"], "9.8 10.6 20.0": ["grapeseed"], "5.4 9.4 5.3": ["tienen"], "8.0 23.2 12.9": ["magickal"], "5.9 2.7 18.2": ["ssp"], "0.8 17.2 1.2": ["swaraj"], "-3.1 7.7 7.0": ["varices"], "3.0 8.3 11.6": ["mati"], "2.2 11.0 10.4": ["unanalyzed"], "-2.3 6.0 -1.1": ["compulsary"], "8.1 8.3 14.2": ["auspiciousness"], "0.5 4.7 7.2": ["underpublicized"], "15.4 7.4 26.2": ["cabeza"], "4.1 -1.6 12.2": ["ediscovery"], "9.6 8.5 3.4": ["grubbier"], "8.4 5.6 11.2": ["joggling"], "-1.1 7.8 4.4": ["tittles"], "6.1 -2.7 12.0": ["tph"], "9.6 27.2 7.1": ["blasphemously"], "16.6 12.9 28.8": ["titmouse"], "10.7 3.9 19.0": ["megafund"], "8.2 26.4 18.6": ["unresisting"], "3.2 22.2 8.4": ["confrontationally"], "2.2 3.6 11.4": ["malaking"], "4.8 5.6 12.7": ["alon"], "7.4 2.0 2.6": ["meteorically"], "7.9 9.5 6.9": ["holism"], "14.8 5.8 14.4": ["norman"], "-7.6 20.6 9.2": ["teshuva"], "6.6 2.5 12.5": ["doobies"], "5.1 1.6 3.9": ["dlls"], "-1.4 5.2 1.2": ["milliamp"], "-3.2 -0.5 3.2": ["levelized"], "5.8 0.9 18.5": ["bumi"], "2.3 1.9 3.8": ["posterolateral"], "6.4 23.9 10.4": ["disturbers"], "8.6 2.2 22.2": ["eba"], "2.5 11.7 12.7": ["upmoves"], "0.3 28.6 9.6": ["audibling"], "5.1 10.6 18.8": ["potsherds"], "13.9 11.6 18.1": ["cleome"], "3.5 12.9 0.2": ["seasonhigh"], "2.6 22.0 0.2": ["pointmen"], "6.6 11.9 16.7": ["matai"], "4.5 20.9 9.6": ["dimensionless"], "4.7 -6.7 0.9": ["aftera"], "-4.6 -0.7 2.1": ["repassed"], "26.8 14.9 2.5": ["superefficient"], "29.1 11.9 20.5": ["allosaurus"], "10.6 0.4 6.9": ["monobloc"], "11.2 4.6 18.0": ["emulsifies"], "8.9 1.4 8.9": ["laters"], "6.6 4.9 1.4": ["ddp"], "3.9 3.6 10.9": ["effuses"], "3.5 1.8 11.2": ["carbonatites"], "23.2 -0.3 12.2": ["corrugate"], "6.6 -0.9 9.3": ["brachial"], "2.8 10.5 8.3": ["inour"], "2.8 24.1 3.7": ["sophists"], "5.9 10.0 14.0": ["roastmaster"], "3.2 9.8 3.1": ["kommt"], "26.0 6.1 12.5": ["blinky"], "0.7 23.8 2.4": ["instigations"], "11.1 8.2 11.6": ["rammy"], "10.0 19.4 7.5": ["backstairs"], "8.2 7.8 10.4": ["cryptogram"], "17.6 16.9 15.6": ["sheerest"], "-8.4 6.9 2.9": ["opinons"], "11.2 7.9 15.5": ["heaver"], "-5.7 9.7 4.5": ["necesarily"], "9.7 2.8 18.6": ["fiddlin"], "12.0 -2.0 13.7": ["italiano"], "0.6 8.0 26.1": ["madeira"], "-1.6 13.0 6.8": ["bioburden"], "5.8 5.9 10.9": ["detangle"], "2.2 19.7 7.2": ["unblushingly"], "14.8 19.6 11.4": ["riddance"], "10.4 3.1 12.1": ["gobbing"], "1.9 17.8 12.9": ["indvidual"], "1.7 -2.1 15.4": ["jeroboam"], "7.8 18.3 13.3": ["seductresses"], "14.5 7.2 3.0": ["goed"], "-0.1 12.4 26.2": ["drawspan"], "-10.1 7.1 4.4": ["reconviction"], "5.9 5.7 -1.9": ["personalizable"], "5.9 4.7 3.2": ["tocreate"], "6.4 -2.2 14.8": ["hynny"], "3.2 11.0 1.5": ["preselectors"], "2.4 9.0 5.9": ["tankering"], "16.7 16.6 33.7": ["copepod"], "5.3 11.7 1.9": ["softkey"], "-4.6 7.2 6.2": ["cytotoxics"], "16.3 12.5 15.5": ["bellboys"], "15.4 23.0 14.2": ["nonhumans"], "13.0 9.9 37.0": ["gyudon"], "-2.1 6.0 -1.7": ["disappearence"], "10.9 17.7 10.8": ["hardballs"], "1.9 -2.5 9.6": ["oedd"], "2.9 13.7 5.9": ["nebulously"], "-8.9 -0.8 4.9": ["adenoidectomy"], "-4.3 21.6 3.3": ["brassage"], "6.4 -0.8 9.4": ["lng"], "-1.8 4.7 12.3": ["karon"], "0.3 8.0 18.4": ["schoolday"], "-1.2 21.1 7.0": ["nonzero"], "8.5 4.6 13.7": ["lhakhang"], "-5.9 10.7 8.6": ["predecisional"], "5.0 8.3 3.4": ["microamp"], "7.2 6.9 12.1": ["parasitologist"], "-9.9 7.9 7.4": ["benzos"], "-7.1 15.0 7.9": ["stenotic"], "4.6 1.9 11.1": ["pmi"], "-4.9 15.8 11.1": ["pulis"], "4.0 -2.3 9.9": ["uncemented"], "2.0 0.5 8.7": ["abotu"], "11.6 6.2 1.1": ["evenutally"], "8.8 1.6 14.6": ["cria"], "15.1 30.1 5.5": ["fuehrer"], "3.6 2.4 11.9": ["shmooze"], "14.8 20.1 16.5": ["pridefully"], "9.6 11.4 10.7": ["microjets"], "-0.2 15.7 0.7": ["intangibly"], "-2.9 6.8 4.4": ["underemphasized"], "3.0 6.7 14.8": ["floriferous"], "-11.4 8.1 1.9": ["thyroiditis"], "5.1 23.6 3.9": ["gaurds"], "10.4 4.1 17.6": ["unpasteurised"], "7.8 11.5 17.0": ["desalinating"], "2.4 19.9 16.7": ["formlessness"], "1.7 5.7 0.0": ["matchs"], "14.6 16.3 22.6": ["jaffa"], "17.1 0.2 9.9": ["stanford"], "19.0 0.9 12.6": ["zorbing"], "15.5 9.3 6.4": ["pluming"], "5.1 4.3 11.5": ["burquini"], "18.6 16.7 12.0": ["amorously"], "5.7 4.6 5.1": ["mobiclear"], "3.2 3.7 5.2": ["bodog"], "3.9 6.5 3.6": ["enduser"], "7.2 14.0 10.6": ["cutler"], "16.7 23.0 20.4": ["yokai"], "9.5 15.5 26.9": ["hibernacula"], "3.7 12.9 8.3": ["editorialising"], "10.1 3.0 23.2": ["patinated"], "8.2 3.7 18.2": ["ngan"], "5.5 9.3 21.7": ["dooryard"], "13.0 11.5 5.9": ["flightworthy"], "8.2 16.4 12.6": ["shogi"], "4.4 -0.4 8.7": ["saar"], "2.9 14.3 1.2": ["summa"], "-5.0 1.5 7.4": ["preforeclosure"], "10.2 4.9 43.8": ["fiddlehead"], "10.3 6.6 31.7": ["primulas"], "5.8 6.5 12.7": ["blb"], "17.8 6.2 13.6": ["oilsand"], "-1.5 8.4 14.0": ["granchildren"], "-1.8 11.0 1.9": ["checkable"], "-7.3 2.8 14.0": ["gonadotropins"], "2.3 11.3 17.8": ["reelin"], "1.8 20.8 10.5": ["overcommitting"], "3.7 10.8 1.1": ["exampled"], "10.1 7.4 19.3": ["osmanthus"], "-10.5 1.4 -2.2": ["ress"], "8.3 33.5 1.6": ["reconaissance"], "15.4 19.3 4.9": ["toyline"], "1.5 7.7 -2.2": ["multiskilled"], "-0.2 4.8 -0.3": ["saidin"], "5.0 -1.9 -0.0": ["freepost"], "15.9 8.1 16.3": ["eyeteeth"], "7.6 5.0 7.8": ["polyclonal"], "-3.3 7.2 -7.3": ["opportuned"], "14.8 14.0 10.6": ["hadrons"], "1.8 0.8 2.8": ["autoinjector"], "6.4 12.4 16.8": ["freeplay"], "1.6 19.6 10.9": ["eyeshot"], "6.0 10.9 17.6": ["bulldogged"], "9.8 -0.1 10.8": ["rollicked"], "8.8 -4.1 15.3": ["ducktail"], "21.4 12.9 10.0": ["drainers"], "-5.3 9.9 7.7": ["antigang"], "-0.0 10.7 3.8": ["philological"], "19.4 8.7 2.5": ["alonside"], "17.2 8.4 23.2": ["daubers"], "-3.4 12.2 7.6": ["rickshawpuller"], "6.3 4.9 14.0": ["handclapping"], "11.8 8.2 6.0": ["patcher"], "-7.1 13.8 1.9": ["agreeance"], "-0.2 14.4 10.6": ["disturbanc"], "7.1 18.1 8.8": ["wakens"], "2.2 2.7 21.6": ["cfu"], "-11.1 14.2 3.3": ["reoccurrences"], "2.3 10.1 16.6": ["saal"], "-1.9 8.8 9.4": ["chf"], "5.7 21.8 5.4": ["fallibilities"], "4.7 6.4 1.9": ["reseated"], "7.3 17.9 2.8": ["inseparability"], "3.6 11.9 31.9": ["baetis"], "6.4 15.3 17.0": ["braggin"], "7.2 1.2 11.6": ["exim"], "8.5 10.3 2.3": ["organzation"], "13.2 4.8 37.1": ["relleno"], "6.0 8.4 11.6": ["middeck"], "6.8 13.8 15.9": ["geomorphological"], "16.5 2.5 24.7": ["scrummy"], "8.6 9.9 9.0": ["hardcoded"], "-0.1 15.3 4.8": ["remonstrates"], "2.4 14.1 10.2": ["hehad"], "14.3 4.7 6.0": ["weltweit"], "-10.8 2.5 8.9": ["reappropriation"], "6.2 16.4 7.6": ["woops"], "13.9 -3.8 3.8": ["rigids"], "16.6 3.8 9.1": ["jawboned"], "1.8 9.5 -5.2": ["annuled"], "-3.8 15.7 6.4": ["esquire"], "15.1 26.8 4.4": ["paranoiacs"], "7.4 10.7 7.1": ["unjaded"], "5.8 13.1 4.3": ["decarbonize"], "7.1 12.5 12.3": ["sarcosine"], "13.2 5.3 16.3": ["metalic"], "-2.0 4.6 -6.4": ["spirtual"], "-3.0 10.7 10.2": ["overstressing"], "4.5 8.2 11.3": ["motocycle"], "-3.0 10.4 4.3": ["epilogues"], "9.8 3.8 28.2": ["amphoras"], "-0.4 -0.9 8.4": ["nites"], "-6.4 11.5 8.3": ["melodist"], "15.0 2.5 6.7": ["whitewalls"], "10.7 12.3 1.8": ["jilts"], "22.5 -0.2 27.2": ["lowboy"], "3.5 6.1 0.8": ["anderen"], "8.5 -2.5 14.6": ["tanktop"], "1.3 11.4 13.8": ["occlusal"], "18.7 16.8 4.5": ["bigest"], "18.6 6.2 20.2": ["taipans"], "11.5 7.3 13.2": ["ragingly"], "-4.1 16.0 1.6": ["carbapenem"], "9.2 7.9 29.5": ["shibori"], "1.9 18.0 1.5": ["cryptanalysis"], "9.5 3.6 -3.4": ["ambassadress"], "-6.1 5.8 35.2": ["embayments"], "-0.2 3.9 5.0": ["chur"], "5.7 1.1 40.2": ["bottarga"], "5.8 7.7 20.8": ["yow"], "-3.8 4.9 10.4": ["daidzein"], "11.0 22.1 2.8": ["collusions"], "3.4 0.4 16.0": ["aro"], "3.0 7.8 12.5": ["byu"], "14.3 12.0 9.1": ["shitloads"], "3.6 5.9 9.7": ["defensibly"], "13.6 25.0 7.2": ["brushback"], "-0.1 -0.1 6.6": ["probates"], "4.6 15.1 8.4": ["procyclicality"], "4.1 13.8 8.3": ["workingclass"], "3.8 1.6 10.2": ["hilltribe"], "3.1 0.4 4.5": ["sigs"], "-1.1 6.2 10.4": ["alaap"], "3.8 9.3 -3.5": ["myvu"], "5.6 2.3 13.3": ["alginates"], "2.9 6.5 10.3": ["protegees"], "4.9 1.4 16.8": ["kota"], "7.9 -0.5 14.3": ["embryological"], "14.6 14.3 3.1": ["collimation"], "22.0 19.8 7.7": ["emptily"], "3.4 1.6 5.5": ["probenecid"], "10.4 14.5 5.9": ["heldentenor"], "2.8 10.8 5.5": ["sparest"], "11.7 10.5 15.1": ["antipodeans"], "8.0 6.7 12.2": ["immer"], "0.4 3.2 22.4": ["oleoresin"], "17.1 21.5 10.7": ["planetoids"], "15.1 23.1 12.9": ["clichs"], "-0.6 10.0 2.6": ["immunodeficiencies"], "-3.6 12.6 13.1": ["lipomas"], "6.7 14.9 2.9": ["inestimably"], "6.3 17.1 18.0": ["whut"], "0.4 13.1 -0.7": ["dislodgement"], "8.1 18.5 4.0": ["beclouded"], "-11.5 28.0 7.9": ["arguer"], "13.6 -0.6 7.0": ["endosurgery"], "10.7 3.2 0.3": ["exisitng"], "15.2 9.5 48.0": ["merganser"], "6.1 10.8 11.5": ["cutlines"], "8.6 17.8 -1.0": ["magine"], "1.7 9.8 16.8": ["huwag"], "18.4 -2.2 17.3": ["crimpers"], "8.3 8.3 7.1": ["kerfluffle"], "-5.2 9.0 21.3": ["phutti"], "12.0 14.4 16.4": ["couloirs"], "-1.5 4.5 16.3": ["masaya"], "11.8 21.5 9.7": ["resistible"], "7.7 3.0 39.9": ["humpies"], "7.7 10.0 10.4": ["overpressured", "bitte"], "5.6 7.6 33.5": ["sisig"], "7.1 12.2 11.0": ["autotuned"], "2.6 16.2 17.5": ["zai"], "7.7 16.9 8.4": ["trued"], "3.6 9.9 3.2": ["miconazole"], "14.9 4.2 -0.3": ["espite"], "0.7 10.9 4.2": ["microvasculature"], "12.9 19.6 9.7": ["nark"], "6.8 27.8 5.2": ["inhumanities"], "5.6 14.6 0.9": ["bedrails"], "17.0 10.8 14.5": ["unjam"], "10.2 16.1 27.0": ["windjammer"], "10.9 37.4 9.7": ["nuclearized"], "10.1 4.1 5.0": ["bayer"], "20.6 -0.7 -3.1": ["aquires"], "9.7 6.0 3.9": ["secondrower"], "7.2 24.3 0.8": ["deminer"], "18.1 9.3 -2.6": ["playstations"], "2.7 8.0 6.0": ["reoccuring"], "19.8 5.3 21.8": ["longneck"], "15.3 12.0 15.6": ["chappy"], "9.9 -0.7 18.1": ["unshaped"], "13.0 13.2 14.3": ["slaughterman"], "4.1 3.6 10.1": ["sandboarding"], "-0.2 9.9 17.2": ["musks"], "9.4 5.6 16.4": ["hulle"], "1.2 11.7 12.1": ["lisps"], "5.7 5.0 15.2": ["mhux"], "-0.7 -3.4 6.3": ["thequarter"], "2.6 14.6 2.7": ["putaways"], "11.5 5.7 27.7": ["fernery"], "0.7 8.0 19.6": ["successional"], "13.6 11.2 26.2": ["cornflowers"], "16.4 11.9 8.1": ["toolbag"], "24.2 7.2 8.2": ["thingamajigs"], "5.7 3.9 33.9": ["sopressata"], "6.4 -0.6 -1.9": ["electrotechnical"], "-6.0 9.9 1.0": ["centerbacks"], "6.5 36.9 2.4": ["terroist"], "10.6 4.3 11.9": ["unguents"], "10.1 6.3 24.7": ["progerin"], "8.6 10.2 24.0": ["lorises"], "13.3 21.9 8.1": ["terribleness"], "-8.1 12.3 4.6": ["sharif"], "23.0 5.2 17.5": ["sixpack"], "4.8 14.8 3.5": ["enitre"], "12.3 8.0 8.6": ["commoditise"], "7.8 15.4 11.6": ["stikes"], "-2.0 1.0 2.4": ["chronobiology"], "21.0 4.1 18.3": ["oinking"], "16.4 7.9 12.5": ["weeny"], "8.3 2.2 2.1": ["migh"], "14.7 5.1 15.5": ["curbstones"], "-4.4 0.8 5.0": ["atresia"], "24.6 20.0 12.3": ["ziggurats"], "2.7 12.5 10.1": ["uncategorized"], "15.2 6.9 7.1": ["bumf"], "-1.6 0.6 5.6": ["estrone"], "14.2 13.8 9.3": ["biosignatures"], "11.5 9.5 4.9": ["nyt"], "0.6 9.2 5.8": ["opengl"], "11.4 32.1 8.3": ["battlezone"], "12.1 5.3 40.1": ["tournedos"], "-0.7 15.5 10.5": ["overexerted"], "10.8 8.5 3.1": ["carrel"], "5.2 15.0 9.5": ["ontheir"], "-1.9 8.7 9.3": ["donnish"], "4.5 2.2 23.0": ["paniolo"], "7.7 11.3 17.8": ["sliminess"], "-2.0 0.4 -3.2": ["eluted"], "0.6 -10.1 2.8": ["resubmissions"], "4.8 14.7 14.9": ["eukaryote"], "21.4 12.2 -1.2": ["thatwould"], "6.7 2.6 -0.7": ["channelizing"], "9.0 11.8 17.8": ["middlin"], "1.8 17.7 17.6": ["sheepishness"], "17.4 16.1 9.1": ["klutziness"], "6.0 1.5 -1.0": ["lockerrooms"], "9.4 13.3 16.3": ["toman"], "7.7 18.3 3.6": ["humilation"], "1.2 15.0 20.3": ["riverways"], "7.5 2.9 13.6": ["tish"], "10.8 8.1 14.3": ["turps"], "17.3 4.6 10.4": ["timelapse"], "-4.8 6.1 6.7": ["casebooks"], "5.9 9.1 12.9": ["propshaft"], "9.8 15.3 11.5": ["forgivably"], "10.0 6.1 33.0": ["chicharon"], "4.1 -2.1 3.3": ["fiji"], "12.3 17.2 4.1": ["kleptocrat"], "6.8 0.1 14.2": ["florins"], "14.0 -1.1 16.6": ["dickered"], "16.1 1.4 21.6": ["udderly"], "6.5 25.0 18.4": ["lesnar"], "-2.9 19.2 5.6": ["townsman"], "2.0 20.4 8.1": ["overpassing"], "6.9 9.8 9.4": ["masculinization"], "15.8 2.0 17.8": ["excrements"], "-4.2 3.5 0.9": ["reccomended"], "16.9 12.1 25.3": ["philodendrons"], "12.3 -0.5 22.5": ["caffe"], "14.3 9.7 23.9": ["baster"], "8.0 17.8 9.8": ["bucs"], "11.9 3.6 9.8": ["rgt"], "-5.7 6.7 9.0": ["producibility"], "-3.3 -2.8 12.3": ["boluses"], "-0.6 17.6 -0.7": ["unscriptural"], "4.1 1.5 19.8": ["haut"], "4.4 -0.4 7.6": ["amsterdam"], "8.9 25.9 2.5": ["exhilarates"], "11.4 5.4 25.1": ["kush"], "1.2 7.7 16.5": ["deworm"], "6.6 6.4 10.5": ["burlier"], "9.7 6.3 10.6": ["marche"], "10.5 13.9 2.3": ["bemobile"], "1.2 9.0 18.8": ["diri"], "7.2 16.8 -3.7": ["condems"], "6.0 14.9 22.4": ["bitting"], "2.9 2.7 14.7": ["antepost"], "11.4 11.3 39.9": ["katsu"], "3.5 15.4 9.8": ["thouroughly"], "-0.2 4.4 0.6": ["gatvol"], "16.7 7.1 34.8": ["lorikeet"], "8.9 5.6 9.9": ["origional"], "5.2 0.2 4.2": ["dotmusic"], "2.9 4.0 6.9": ["interpleader"], "2.8 5.0 8.6": ["dispiritingly"], "9.8 18.5 18.1": ["harridans"], "6.0 11.4 5.1": ["deskphone"], "-3.5 7.9 5.8": ["deduplicating"], "1.6 8.7 14.5": ["ganoon"], "21.9 14.0 22.0": ["mantled"], "-3.2 9.7 5.0": ["petrodiesel"], "0.4 4.9 16.4": ["mancation"], "6.8 12.9 13.9": ["campness"], "-1.9 1.7 -0.8": ["contribued"], "5.1 14.4 18.3": ["vegetations"], "6.4 14.0 4.4": ["humanisation"], "-2.4 4.8 11.2": ["charettes"], "-1.3 17.4 8.6": ["apartness"], "6.8 14.3 6.2": ["slopfest"], "-0.2 -7.4 16.0": ["piu"], "0.6 10.1 12.7": ["epidote"], "6.9 12.3 24.0": ["halite"], "0.9 15.4 11.3": ["triology"], "9.5 8.6 51.0": ["abalones"], "7.7 11.8 25.3": ["mandevilla"], "4.2 19.0 11.5": ["extratropical"], "13.0 1.4 7.5": ["sportsground"], "9.8 36.2 4.9": ["outwait"], "13.3 5.4 12.1": ["daypacks"], "-6.1 6.2 -1.7": ["noradrenergic"], "19.2 16.7 28.3": ["quoll"], "10.6 -4.3 0.4": ["devicemakers"], "-5.7 2.4 14.4": ["dystocia"], "6.4 12.7 9.0": ["dishevelment"], "7.1 3.8 28.0": ["beaujolais"], "-2.3 5.6 4.0": ["duathlete"], "7.3 13.5 21.4": ["felucca"], "3.4 -0.9 -4.5": ["zopiclone"], "14.2 13.4 15.8": ["prickliest"], "-3.1 4.8 14.3": ["newport"], "7.5 8.2 23.2": ["skinners"], "-6.6 15.1 -6.1": ["resiled"], "8.8 32.0 15.1": ["mercilessness"], "0.6 8.5 20.3": ["huma"], "5.5 14.8 10.1": ["rootin"], "8.2 5.3 24.2": ["muttonchops"], "11.4 12.7 32.0": ["loquat"], "10.9 8.7 8.1": ["hellers"], "1.8 5.2 8.9": ["ality"], "5.3 17.7 18.6": ["legspinners"], "-2.0 8.0 34.6": ["prefishing"], "5.8 1.7 -3.8": ["twoyears"], "5.9 5.8 8.8": ["racecards"], "-0.2 21.6 4.5": ["undruggable"], "3.3 10.5 9.0": ["imposible"], "8.9 14.5 15.2": ["curtsying"], "13.5 9.9 19.2": ["headachy"], "15.8 8.0 19.4": ["snowscape"], "-1.9 7.9 6.6": ["unfavorability"], "-1.0 3.6 17.8": ["cotillions"], "1.8 5.9 5.7": ["testiment"], "0.4 -1.0 2.5": ["buspirone"], "9.1 12.1 10.8": ["filetype"], "0.1 3.0 13.1": ["bukas"], "0.0 23.6 4.0": ["arrestable"], "18.9 29.4 11.4": ["stealthiest"], "18.0 19.1 19.1": ["superfly"], "7.5 14.4 7.0": ["mimesis"], "-5.7 -3.2 -1.9": ["rescoring"], "7.9 7.6 10.1": ["chainset"], "13.9 7.2 22.2": ["plucker"], "7.5 20.4 10.6": ["outscrapped"], "8.2 14.7 10.5": ["grouts"], "11.0 9.4 36.1": ["muskoxen"], "8.0 11.6 9.2": ["microkeratome"], "8.0 3.1 8.4": ["tand"], "6.7 13.9 16.1": ["biretta"], "5.4 5.6 20.6": ["freezable"], "-6.1 2.1 13.8": ["coxing"], "8.4 11.6 18.1": ["bardic"], "8.6 -0.6 1.5": ["biorenewable"], "-2.6 12.8 6.1": ["ballstriking"], "0.2 7.2 5.2": ["considerd"], "2.8 8.4 8.7": ["perceivably"], "8.0 7.1 34.1": ["tastily"], "1.8 9.9 8.2": ["kyon"], "-5.3 14.5 -2.1": ["immunomodulation"], "20.5 13.2 37.4": ["flyrod"], "-0.2 6.2 4.0": ["metalled"], "11.2 5.3 10.9": ["sprightliness"], "-6.3 -2.3 9.2": ["liposculpture"], "-2.2 8.4 1.0": ["braindumps"], "15.6 5.9 21.7": ["porkulus"], "0.3 2.9 1.4": ["committtee"], "8.1 -0.1 5.5": ["cablevision"], "0.0 7.1 2.5": ["reregistering"], "11.6 1.6 17.7": ["cuppas"], "16.1 17.5 11.6": ["overamped"], "6.2 16.3 32.2": ["fowling"], "17.5 22.5 35.0": ["skuas"], "1.5 3.4 5.2": ["flupirtine"], "-4.4 7.3 8.7": ["cubmaster"], "-6.3 18.8 0.6": ["sucide"], "7.9 6.6 33.3": ["estero"], "21.2 3.8 6.9": ["tocks"], "-6.0 7.7 5.8": ["trai"], "5.5 16.4 5.7": ["happenning"], "29.4 9.0 17.7": ["santas"], "11.8 19.1 9.7": ["andthen"], "7.0 9.1 13.2": ["harley"], "1.2 15.3 -0.3": ["choise"], "-4.0 15.0 4.8": ["proccess"], "5.1 8.1 3.6": ["tuberculin"], "-2.0 1.7 -0.3": ["chage"], "18.8 18.0 21.7": ["squirters"], "0.7 5.0 8.9": ["addback"], "11.2 25.0 3.4": ["themelves"], "11.1 6.9 4.3": ["informa"], "6.7 16.5 13.8": ["kutcha"], "-1.2 7.9 13.4": ["wallrock"], "3.0 15.8 9.4": ["whiteman"], "18.0 5.2 16.0": ["refridgerator"], "12.3 21.1 10.9": ["graven"], "-0.7 16.3 19.6": ["rhizobia"], "7.4 6.6 5.6": ["pricelist"], "7.6 19.7 -4.2": ["hinter"], "2.4 13.7 37.1": ["steelheaders"], "-1.7 5.8 6.0": ["admi"], "10.5 10.0 9.5": ["headful"], "5.3 15.1 5.7": ["goalbox"], "7.7 19.8 8.3": ["hajjis"], "11.8 2.7 17.7": ["gros"], "-6.0 7.0 15.3": ["nonspeaking"], "0.0 14.5 3.8": ["notbe"], "7.6 14.3 8.8": ["hypeman"], "6.9 8.4 14.9": ["lentiviruses"], "5.3 11.8 9.2": ["iad"], "-3.8 9.6 0.5": ["nda"], "11.0 7.0 22.4": ["wastin"], "3.8 10.8 4.4": ["proactiveness"], "21.6 17.3 11.4": ["joylessly"], "3.5 6.2 3.9": ["tennant"], "1.2 10.2 4.8": ["htis"], "-4.5 17.2 6.2": ["hermeneutical"], "5.3 10.0 -8.9": ["officier"], "11.3 2.8 10.3": ["vamoosed"], "-3.3 14.9 -0.3": ["immedately"], "7.0 6.2 5.2": ["andtheir"], "-2.3 5.1 5.9": ["benn"], "6.0 6.3 11.6": ["kuya"], "3.2 17.0 8.9": ["erogenous"], "6.6 9.8 12.0": ["meterological"], "-12.3 -3.9 7.4": ["schoolyear"], "7.0 6.8 14.8": ["deadlifts"], "3.9 8.3 40.1": ["baccala"], "15.3 -0.3 15.5": ["ebonized"], "22.6 6.2 19.7": ["whispy"], "15.0 5.0 -1.9": ["nextgeneration"], "3.5 6.4 24.5": ["heucheras"], "19.5 5.4 1.9": ["photosharing"], "1.6 16.6 9.6": ["fiducial"], "9.5 10.3 22.7": ["gamelands"], "19.2 2.3 2.6": ["siemens"], "-3.8 6.5 15.7": ["lulus"], "1.8 8.0 -3.6": ["datalogging"], "0.4 3.6 1.5": ["prefixing"], "-8.9 -9.3 1.0": ["elegible"], "13.8 -2.1 8.6": ["concreter"], "13.6 5.1 8.5": ["chatelaine"], "7.0 6.2 -1.4": ["eveninger"], "9.8 17.1 1.4": ["geohot"], "12.8 -3.1 11.7": ["noche"], "-9.6 14.0 5.7": ["strobilurin"], "-0.2 7.9 7.5": ["giftable"], "1.6 7.0 8.0": ["sunt"], "10.4 13.7 13.5": ["jonesin"], "9.9 19.2 2.0": ["declassifies"], "3.3 0.6 11.1": ["ched"], "3.1 7.6 11.2": ["zzzzz"], "16.8 21.0 8.7": ["charioteers"], "16.4 4.4 4.1": ["newco"], "4.2 5.8 7.0": ["outduelling"], "1.4 9.2 7.6": ["misdeclaration", "hilliest", "statewise"], "-1.3 17.7 11.3": ["lenity"], "5.0 6.8 12.4": ["toolies"], "-1.7 12.1 1.9": ["commment"], "9.6 5.3 17.7": ["saddlebred"], "4.2 7.4 3.9": ["retitle"], "0.4 -9.1 11.4": ["playscheme"], "9.2 8.3 10.7": ["haas"], "-1.2 0.1 7.9": ["resoled"], "14.2 8.7 51.8": ["threadfin"], "-1.2 19.0 7.1": ["trustor"], "17.4 30.3 6.7": ["assasin"], "-4.3 10.5 12.7": ["headguard"], "14.9 9.5 10.1": ["unum"], "-3.5 5.1 5.6": ["monopolar"], "-3.8 5.0 -2.8": ["correspondance"], "4.1 2.1 2.8": ["fll"], "1.7 4.6 5.2": ["loupes"], "15.2 -3.2 10.0": ["neutraceuticals"], "3.5 8.1 -1.6": ["purifications"], "13.3 -0.8 5.3": ["mjunction"], "-2.8 8.9 0.2": ["serialising"], "7.3 -5.4 21.0": ["tempe"], "9.2 -2.7 -2.3": ["chemogenomics"], "14.6 1.0 13.7": ["sational"], "14.5 13.9 22.7": ["dolerite"], "6.5 18.2 -1.3": ["misidentifies"], "17.5 16.0 9.3": ["subtlely"], "2.6 7.5 9.6": ["saz"], "7.9 1.2 34.3": ["pandesal"], "1.8 9.6 11.8": ["diminuendo"], "0.3 4.6 5.8": ["substitutability"], "6.1 0.9 14.2": ["reground"], "1.4 13.7 3.7": ["subvertical"], "-0.6 -3.1 -1.2": ["icstars"], "2.2 12.8 5.8": ["epl"], "4.3 8.8 11.4": ["wfa"], "3.9 21.4 11.3": ["encroacher"], "13.9 4.1 11.2": ["brickies"], "-2.8 5.0 16.7": ["batas"], "8.2 17.0 22.6": ["tast"], "-10.0 12.0 -2.0": ["polygraphed"], "12.5 16.7 5.8": ["flypasts"], "3.6 7.8 43.6": ["bottomfishing"], "10.8 5.3 16.3": ["oliver"], "7.8 7.7 32.8": ["bryozoans"], "0.4 10.6 0.9": ["excellences"], "6.4 -0.4 9.8": ["sobeit"], "0.4 13.4 10.1": ["strokeplayer"], "4.0 23.4 9.7": ["windshear"], "9.1 9.7 11.6": ["sleeze"], "0.4 15.0 17.9": ["unsurveyed"], "10.2 14.6 22.5": ["choicer"], "8.9 13.7 11.8": ["scrollbars"], "0.2 7.9 7.1": ["reburials"], "7.0 6.6 18.6": ["unloaders"], "4.6 5.2 7.5": ["ords"], "10.5 13.4 11.2": ["mademoiselle"], "16.6 8.4 12.3": ["rhomboid"], "6.8 -1.9 7.5": ["accessway"], "11.7 11.2 20.9": ["maori"], "9.0 21.8 13.9": ["imperially"], "-7.7 23.6 2.0": ["dawah"], "17.1 3.0 13.9": ["glamazons"], "0.1 8.3 19.9": ["shahi"], "15.7 22.1 17.2": ["sjamboks"], "5.8 -1.4 24.3": ["mentha"], "10.8 19.2 20.6": ["hoopoe"], "10.8 -4.6 9.7": ["neglible"], "13.1 12.3 17.2": ["hallucinogenics"], "10.3 1.7 3.1": ["esc"], "1.8 18.4 7.5": ["fabregas"], "-9.5 6.9 38.4": ["bluefishing"], "20.3 16.9 7.9": ["snootily"], "10.9 7.4 8.9": ["nanodevice"], "9.6 17.6 6.4": ["arrester"], "14.7 24.3 16.6": ["shipborne"], "10.2 21.6 12.2": ["icosahedron"], "-8.5 0.5 6.4": ["cient"], "13.7 6.9 6.3": ["stickering"], "10.8 14.3 20.4": ["lianas"], "8.3 9.4 1.7": ["etisalatetisalat"], "8.7 14.6 2.1": ["backpeddling"], "2.4 2.7 16.9": ["drypoint"], "13.0 13.8 18.6": ["shrubberies"], "9.9 5.5 3.1": ["werd"], "-6.4 -3.5 4.4": ["prolotherapy"], "20.0 10.7 14.0": ["peristyle"], "7.0 -1.6 6.5": ["edt"], "-0.4 12.7 7.9": ["transcendentalism"], "10.2 9.6 11.2": ["agbada"], "6.6 16.5 10.3": ["pisser"], "6.1 -1.1 22.1": ["cookoffs"], "13.9 10.2 14.1": ["glomming"], "2.9 8.9 6.7": ["transportion"], "6.9 4.2 31.5": ["softshell"], "21.3 11.2 21.7": ["dauber"], "-5.7 12.6 7.5": ["actualresults"], "3.9 -1.1 -0.7": ["resurgance"], "8.5 10.8 15.7": ["quadbike"], "-0.5 19.1 0.6": ["dialogical"], "6.6 10.7 11.2": ["estar"], "-1.5 -6.7 -3.8": ["techical"], "14.2 9.2 8.5": ["rambunctiously"], "3.2 8.4 32.9": ["undercook"], "2.7 6.0 33.5": ["stillwater"], "13.7 8.2 9.1": ["garrotted"], "4.9 13.0 8.5": ["jad"], "6.6 -2.2 41.3": ["capellini"], "-4.8 -3.3 5.4": ["rediscount"], "-4.5 9.2 -5.3": ["exemplarily"], "15.1 1.1 15.1": ["ific"], "-2.2 11.4 15.6": ["ryu"], "4.9 9.6 3.7": ["admistration"], "4.1 3.1 10.5": ["yeol"], "-1.0 0.9 8.0": ["ammenities"], "-1.5 12.5 4.0": ["denaturalization"], "6.8 16.2 16.0": ["shoulderblocks"], "8.4 5.2 23.6": ["ribbers"], "7.5 8.8 3.2": ["powerpack"], "5.5 -1.2 25.4": ["muscovado"], "-2.0 15.1 2.5": ["livejournal"], "3.2 5.5 7.0": ["roundrobin"], "5.8 10.9 11.3": ["filipino"], "7.8 11.6 11.5": ["insulative"], "13.1 13.8 16.6": ["conventiongoers"], "3.3 17.5 -0.1": ["openhanded"], "0.3 6.7 6.7": ["bigamous"], "0.3 10.7 19.6": ["ganito"], "13.8 12.1 29.9": ["parboil"], "2.2 7.2 6.7": ["trainspotting"], "16.8 12.2 12.8": ["sailboarding"], "2.5 3.9 3.7": ["vue"], "-7.1 6.8 9.7": ["externment"], "20.5 11.2 18.2": ["plushie"], "19.3 13.2 21.3": ["jungly"], "11.0 4.6 18.5": ["faunas"], "1.6 -0.6 4.7": ["businessdigest"], "0.5 6.3 5.0": ["fermion"], "21.1 -2.6 21.8": ["tbl"], "7.8 3.9 19.2": ["palapas"], "-6.8 9.6 4.1": ["endogenously"], "-2.2 12.5 -2.8": ["engagment"], "6.6 18.2 19.7": ["unpruned"], "4.6 -2.9 16.1": ["posadas"], "8.5 12.5 8.9": ["sukkahs"], "-1.2 -0.5 1.8": ["procede"], "4.8 9.9 23.7": ["vitex"], "3.6 10.4 13.8": ["filaria"], "-4.9 4.5 -0.1": ["compensability"], "8.5 2.1 9.2": ["bookbinders"], "4.8 7.9 9.5": ["atrasentan"], "10.1 22.6 18.7": ["chibi"], "12.5 5.2 12.9": ["blether"], "18.3 3.3 14.1": ["wedgy"], "6.1 8.8 6.3": ["peop"], "7.8 3.0 42.1": ["dipnetters"], "4.7 3.9 0.1": ["endocannabinoid"], "3.1 12.4 3.6": ["oppposition"], "17.7 6.1 8.1": ["chatterati"], "15.6 8.9 10.9": ["manbag"], "2.6 7.5 11.3": ["hamate"], "3.5 13.7 5.4": ["precident"], "-3.8 9.9 1.6": ["capacitating"], "2.2 8.5 8.7": ["supination"], "5.7 18.4 21.9": ["stolons"], "6.6 8.8 13.5": ["wrestlemania"], "3.2 4.4 28.7": ["poha"], "6.6 6.3 4.4": ["openminded"], "0.1 26.0 5.7": ["gnosis"], "14.7 4.9 8.4": ["highflyers"], "-5.3 7.1 15.4": ["varicoceles"], "2.0 0.8 3.3": ["nettsteder"], "6.5 15.5 9.5": ["macing"], "9.3 3.4 7.5": ["jaunted"], "13.1 20.3 1.7": ["bootlicker"], "12.4 7.2 24.9": ["striders"], "0.1 22.0 22.5": ["nutsedge"], "0.0 16.9 4.9": ["gendercide"], "7.0 9.6 7.1": ["bioretention"], "10.4 7.1 4.6": ["microprobe"], "1.7 8.9 13.5": ["percentagewise"], "4.4 9.1 7.7": ["casued"], "5.4 14.8 8.9": ["ghettoizing"], "-1.1 17.7 2.5": ["priorty"], "2.9 8.4 12.0": ["chemotheraphy"], "13.1 20.3 9.0": ["kitbags"], "17.5 12.9 14.5": ["twilit"], "9.2 1.8 2.6": ["bioconversion"], "2.9 1.2 7.5": ["kers"], "22.3 15.9 12.8": ["vapourised"], "4.4 12.1 7.4": ["glomerulus"], "8.4 8.2 17.9": ["ocassionally"], "-0.5 6.2 4.4": ["historial"], "0.3 -0.6 10.7": ["quitlines"], "-4.7 6.2 2.5": ["implanters"], "20.6 2.9 27.4": ["cobb"], "14.6 14.3 11.1": ["walla"], "4.6 22.7 14.8": ["dictatorially"], "-0.4 16.1 -4.0": ["whn"], "18.4 9.2 8.5": ["gatehouses"], "7.5 1.4 31.7": ["weighmaster"], "16.1 -1.0 8.4": ["anticorrosion"], "3.5 16.8 13.5": ["bacause"], "22.9 15.7 14.6": ["mountebanks"], "15.7 6.7 10.2": ["jeu"], "4.7 10.5 2.7": ["collimators"], "10.9 4.6 7.5": ["outragous"], "7.5 5.7 3.1": ["uppercrust"], "3.9 24.7 8.8": ["dualist"], "7.0 14.2 7.4": ["whackjob"], "-7.4 15.5 19.3": ["pinner"], "8.5 -1.5 10.5": ["securites"], "9.7 12.8 5.8": ["biodetection"], "7.4 7.2 21.1": ["selvage"], "10.2 6.5 12.5": ["flourmill"], "2.5 -4.7 -7.6": ["amember"], "7.5 4.4 24.5": ["bodyboards"], "0.2 9.0 3.1": ["conceptualizations"], "7.1 4.9 13.7": ["multichip"], "16.6 0.6 6.5": ["bef"], "7.0 17.8 2.5": ["applaudable"], "1.4 12.6 6.0": ["bylane"], "11.6 13.3 6.4": ["arrestor"], "9.0 6.8 14.8": ["cowherds"], "8.6 8.6 13.5": ["burkini"], "-0.1 -5.1 1.4": ["hymenoplasty"], "-1.1 1.2 2.8": ["androgenic"], "6.9 11.1 14.6": ["jayega"], "8.7 -0.6 28.2": ["migas"], "7.4 13.1 9.8": ["humouring"], "-4.9 16.5 13.0": ["reflooded"], "-6.8 10.2 -0.4": ["retranslated"], "6.6 13.4 6.3": ["damge"], "10.0 10.2 36.4": ["cuke"], "5.8 17.8 19.4": ["squishier"], "10.3 5.1 22.5": ["physiologies"], "0.5 16.3 8.5": ["inbounder"], "17.1 20.3 20.6": ["hussies"], "11.1 6.9 27.6": ["foody"], "9.6 15.3 9.2": ["backheels"], "-4.4 -1.7 11.3": ["nondegree"], "16.1 23.9 21.2": ["birdbrain"], "2.2 10.7 7.3": ["ait"], "6.1 -3.3 10.5": ["winn"], "5.7 9.5 46.8": ["groundfishermen"], "12.3 -0.4 7.5": ["xtreme"], "12.9 14.2 24.5": ["crurotarsans"], "6.5 5.3 29.0": ["gao"], "6.5 14.1 14.2": ["barotrauma"], "9.7 17.9 8.8": ["sahibs"], "1.8 11.7 16.3": ["doga"], "5.4 0.4 18.6": ["beary"], "11.8 10.9 3.4": ["waveband"], "12.0 10.3 1.8": ["supernormal"], "14.3 4.8 18.5": ["reet"], "2.4 4.1 23.5": ["tuong"], "16.9 15.2 15.8": ["piledrivers"], "23.7 5.3 9.7": ["plummetting"], "2.8 14.1 11.9": ["blas"], "3.0 6.0 14.9": ["archaeal"], "10.6 11.7 10.5": ["financialisation"], "-2.6 11.4 9.4": ["synuclein"], "-8.9 12.2 13.3": ["scrupulousness"], "2.8 1.2 1.4": ["housewrap"], "11.5 10.5 22.2": ["footbag"], "-6.3 7.3 5.3": ["bandobust"], "7.3 9.5 13.7": ["crowdpleaser"], "5.8 10.5 48.1": ["swordfishing"], "6.5 14.1 4.3": ["shellackings"], "-8.1 3.5 0.1": ["serogroup"], "21.4 14.1 17.5": ["whatsit"], "1.9 10.9 13.5": ["ginawa"], "17.1 -1.7 25.6": ["pluckers"], "4.0 17.9 14.0": ["logicians"], "5.4 -0.1 2.4": ["manometer"], "2.9 3.0 9.1": ["francis"], "10.4 6.7 7.8": ["datastream"], "15.7 2.6 -0.8": ["offiicals"], "-0.0 13.3 5.5": ["footnoting"], "13.2 2.3 27.0": ["saimin"], "2.1 10.4 4.7": ["themto"], "5.9 16.9 6.5": ["agai"], "14.7 4.3 16.5": ["xing"], "17.6 20.4 17.8": ["rapaciously"], "3.2 6.1 5.9": ["vivek"], "11.3 19.5 36.2": ["pokeweed"], "15.2 9.9 17.5": ["alotta"], "-2.7 7.7 9.4": ["cnt"], "4.5 14.1 7.6": ["krishna"], "10.7 3.8 42.8": ["scad"], "1.1 9.6 18.8": ["assam"], "0.2 8.3 9.6": ["polyploidy"], "3.8 6.7 9.2": ["tcpdump"], "16.5 13.7 5.7": ["overregulating"], "0.6 4.1 8.5": ["arun"], "10.7 -1.7 28.5": ["gordita"], "3.0 -1.1 6.8": ["brakewoman"], "3.2 6.1 7.0": ["akan"], "6.8 3.8 23.7": ["motoryachts"], "14.5 4.3 18.5": ["psychedelically"], "8.0 13.8 9.3": ["rofl"], "7.6 12.9 10.5": ["doxology"], "-6.1 -0.4 6.8": ["eosinophilia"], "18.0 20.5 36.1": ["gars"], "-0.3 10.6 4.8": ["fanz"], "8.2 3.7 13.6": ["quarto"], "8.5 4.0 16.8": ["resprayed"], "8.1 2.7 21.4": ["flor"], "21.0 13.7 29.0": ["doubloon"], "17.4 3.5 17.2": ["cruiseliner"], "19.7 6.7 26.0": ["teethed"], "0.4 2.7 0.4": ["documenta"], "12.9 20.7 42.5": ["junco"], "13.2 8.3 14.8": ["overprocessed"], "-4.5 -4.4 11.3": ["cosmesis"], "3.9 11.9 -2.0": ["momentously"], "6.7 9.9 11.9": ["uid"], "0.8 8.3 4.0": ["redetermined"], "6.8 13.0 6.7": ["liitle"], "9.6 0.2 8.5": ["minneapolis"], "0.6 8.0 9.1": ["lineback"], "-1.9 12.4 -0.1": ["inflecting"], "16.7 2.1 4.9": ["targa"], "11.7 1.2 6.9": ["buisiness"], "8.1 -7.9 -4.5": ["exective"], "-2.6 -1.3 3.2": ["lawer"], "11.9 2.7 18.4": ["hardtails"], "-6.8 8.7 4.7": ["quinolone"], "11.0 19.0 1.3": ["recue"], "10.4 -7.1 12.1": ["basques"], "-0.1 -0.8 6.0": ["hindfoot"], "5.2 9.3 12.8": ["seventieth"], "5.9 2.7 0.2": ["epothilones"], "14.0 10.7 14.5": ["occasionaly"], "15.8 5.8 31.7": ["unsmoked"], "9.0 8.0 14.8": ["tokers"], "-0.7 12.0 11.4": ["gliadin"], "-2.2 9.3 9.3": ["diwaniyas"], "1.7 12.4 15.1": ["uncleanness"], "3.5 15.4 3.8": ["intellectualise"], "13.5 2.2 13.1": ["housecoats"], "23.7 4.1 32.1": ["trawlerman"], "5.1 18.4 19.5": ["tailgaiting"], "-7.3 -5.5 -0.7": ["cinacalcet"], "-0.4 23.6 7.8": ["burqua"], "4.7 17.9 19.0": ["hapkido"], "7.6 8.2 17.3": ["gabbros"], "2.3 25.6 4.8": ["putschist"], "12.6 14.8 25.0": ["butternuts"], "6.2 2.5 20.1": ["dichroic"], "22.2 13.8 18.9": ["schmoozers"], "3.7 5.2 11.7": ["weekending"], "16.4 12.3 3.4": ["modchip"], "4.8 15.1 12.9": ["helpmeet"], "-5.7 -5.1 -6.0": ["focuse"], "8.8 0.5 2.5": ["drang"], "15.7 7.0 10.2": ["tarriffs"], "10.7 10.2 6.1": ["baronetcy"], "2.6 15.9 17.5": ["toooo"], "0.6 27.9 0.7": ["facilely"], "15.1 3.5 12.5": ["ultradeep"], "6.3 8.2 15.5": ["tablelands"], "4.2 13.1 8.6": ["tawaf"], "9.0 17.8 5.8": ["tryingto"], "9.8 13.6 19.6": ["cervezas"], "2.9 16.0 7.8": ["dard"], "13.1 8.4 12.1": ["glossily"], "14.7 11.0 44.5": ["powerbait"], "-3.1 6.4 11.2": ["misdemeanants"], "3.5 1.7 20.6": ["trickler"], "8.4 9.9 16.0": ["bora"], "13.3 6.5 37.0": ["chocolately"], "10.4 8.0 27.4": ["tsu"], "12.7 6.6 22.2": ["smokable"], "-0.6 7.1 -1.1": ["upconverts"], "14.9 24.9 22.4": ["bubbas"], "10.8 6.9 3.2": ["compe"], "12.1 -0.6 11.4": ["floricultural"], "13.0 8.0 16.4": ["gemlike"], "9.0 8.1 6.4": ["spendaholic"], "2.8 5.6 10.5": ["ssd"], "1.4 -1.4 3.4": ["lanthanide"], "-6.5 1.7 1.0": ["protem"], "14.3 9.1 13.3": ["ologists"], "7.8 19.4 13.3": ["problemo"], "7.7 10.5 3.6": ["crossdresser"], "4.7 3.1 10.1": ["opti"], "14.2 2.0 9.7": ["moptop"], "14.9 16.2 16.5": ["backslap"], "13.1 21.9 17.8": ["datura"], "4.7 4.2 30.0": ["buri"], "2.7 7.2 6.5": ["nunca"], "14.0 5.4 18.9": ["trundler"], "18.8 18.8 13.2": ["jabbers"], "14.1 7.4 7.9": ["sexualise"], "-0.9 7.7 8.9": ["hebrew"], "8.8 10.7 7.7": ["underwires"], "9.0 9.5 7.5": ["flic"], "12.1 -1.3 9.2": ["nueva"], "22.0 11.3 20.3": ["fattie"], "-2.0 -6.4 -4.9": ["encourged"], "10.2 1.8 10.7": ["sgl"], "7.7 8.2 13.0": ["hayden"], "2.3 0.2 1.6": ["spectrophotometry"], "3.5 3.7 10.6": ["centrefielder"], "7.0 8.2 23.7": ["rou"], "6.7 8.3 3.2": ["strengthener"], "9.5 7.7 5.2": ["ironmonger"], "5.9 8.4 8.8": ["tubule"], "-1.0 12.4 11.5": ["resegregated"], "-3.9 11.3 8.9": ["inconvience"], "2.8 7.3 7.3": ["untampered"], "19.1 5.1 11.5": ["ferrofluid"], "4.7 3.9 14.4": ["hampshire"], "9.8 12.8 12.6": ["shoplifts"], "-6.7 7.2 8.3": ["duathletes"], "4.5 13.1 7.6": ["raytracing"], "16.2 -0.4 21.1": ["cafs"], "-3.3 13.4 6.2": ["contingently"], "6.3 7.7 7.0": ["humerous"], "5.6 9.8 6.3": ["courter"], "0.0 9.0 9.9": ["theatregoing"], "17.0 10.0 4.9": ["underdelivering"], "-0.2 4.9 8.9": ["cato"], "23.9 10.2 10.0": ["ubiquitious"], "6.7 7.1 12.6": ["stablehands"], "3.9 5.2 10.1": ["peroxidase"], "2.8 -9.4 8.0": ["atwo"], "6.9 5.3 27.6": ["cashewnut"], "10.2 0.7 8.4": ["trendspotter"], "7.9 18.3 16.2": ["outproduce"], "17.5 7.6 11.7": ["greenwashed"], "11.8 -5.9 4.9": ["nih"], "8.8 7.8 43.2": ["redfin"], "-6.3 -3.6 2.1": ["fiveyears"], "-6.6 5.3 4.9": ["nostro"], "5.8 7.5 0.9": ["spliting"], "13.6 3.2 4.2": ["nonautomotive"], "21.2 20.8 29.3": ["eskimo"], "19.1 5.3 17.2": ["watusi"], "2.6 6.3 8.0": ["expressionists"], "1.8 10.8 15.4": ["volcanogenic"], "11.3 17.2 3.6": ["aeon"], "12.0 16.7 18.3": ["amphibolite"], "4.9 15.7 6.5": ["rotationally"], "5.8 4.9 13.2": ["jolie"], "12.1 17.7 26.5": ["larches"], "0.6 2.2 5.9": ["brava"], "2.7 14.8 8.4": ["doubleton"], "10.9 0.1 6.3": ["gasketing"], "15.1 16.2 18.8": ["yippy"], "2.8 0.7 0.9": ["organistions"], "1.9 -0.4 -6.0": ["ept"], "11.4 4.1 27.1": ["pirogi"], "6.7 23.7 3.9": ["incompressible"], "14.7 17.3 4.2": ["distractor"], "19.4 30.7 9.0": ["malignantly"], "9.8 17.3 11.2": ["outwaited"], "-1.7 3.2 9.0": ["screenprinters"], "16.1 17.9 31.1": ["plantlife"], "10.4 9.0 10.5": ["expensiveness"], "3.4 16.5 8.8": ["commonplaces"], "10.3 -8.1 5.8": ["dealine"], "4.3 2.7 22.3": ["unya"], "11.2 8.9 10.8": ["smokiest"], "10.4 15.5 17.8": ["undocks"], "0.6 -1.1 1.5": ["dnp"], "10.7 11.3 7.8": ["grovelled"], "7.8 -2.1 2.4": ["incluing"], "-1.6 20.8 9.0": ["amicability"], "0.2 7.0 10.4": ["scorable"], "1.5 6.3 8.8": ["echogenic"], "13.9 11.8 10.1": ["oul"], "12.3 6.1 1.3": ["deptt"], "5.2 -0.8 6.8": ["igaming"], "-6.5 -2.8 10.9": ["reapprove"], "21.3 7.2 20.0": ["tined"], "2.2 17.7 4.7": ["inate"], "6.5 15.2 1.8": ["hehas"], "-2.1 -2.7 6.1": ["caso"], "-0.4 7.2 18.3": ["adrian"], "10.0 18.8 10.3": ["phising"], "-0.9 0.8 12.9": ["mujer"], "9.2 10.5 15.0": ["sterndrive"], "5.5 0.3 6.1": ["smartwater"], "-4.4 20.7 3.4": ["transpeople"], "14.8 16.9 12.2": ["zanies"], "8.0 10.3 32.7": ["kreplach"], "5.0 3.8 9.4": ["regrinding"], "5.0 14.1 7.5": ["interleave"], "7.2 17.1 37.4": ["surfcasters"], "0.0 5.5 8.6": ["ahmed"], "4.1 13.8 0.3": ["willingess"], "-6.4 28.2 3.5": ["radicalizes"], "-3.9 2.4 11.3": ["dhan"], "11.6 22.4 17.6": ["retreive"], "9.8 5.5 12.1": ["menisci"], "22.3 2.0 16.6": ["ceilinged"], "-0.7 -0.5 -1.6": ["sutureless"], "14.2 -4.5 12.3": ["plexi"], "3.9 21.4 7.3": ["vulgarism"], "11.2 13.3 25.9": ["dracaena"], "4.8 16.4 5.1": ["mistyping"], "-8.2 2.0 15.5": ["brokens"], "1.4 16.5 1.9": ["hagiographies"], "-9.7 23.3 -0.1": ["refusers"], "13.0 18.5 13.0": ["ladykiller"], "4.7 8.4 22.0": ["lightkeeper"], "-7.4 11.8 7.4": ["carryforwards"], "8.5 24.3 15.0": ["seapower"], "5.4 2.5 11.8": ["floorplates"], "13.3 16.1 -0.8": ["intead"], "2.0 -0.5 2.2": ["suitings"], "-2.7 1.0 16.0": ["patti"], "1.9 -2.3 9.4": ["fleadh"], "0.9 20.7 3.5": ["timidness"], "6.2 -5.4 0.5": ["offre"], "15.4 3.0 4.5": ["shaftless"], "-3.3 20.9 5.5": ["interpenetration"], "6.9 13.0 -2.0": ["pseudonymously"], "1.1 4.0 13.4": ["ridgling"], "-6.3 1.9 3.5": ["postsurgery"], "5.5 6.6 6.6": ["ledes"], "10.2 14.0 10.2": ["unpeg"], "3.8 5.7 4.2": ["gametracker", "monochromator"], "18.5 8.3 22.8": ["cayman"], "-2.8 -5.2 5.1": ["resid"], "26.7 13.3 15.5": ["razorblades"], "2.4 10.6 17.4": ["kumkum"], "-1.9 10.8 13.1": ["outfielding"], "0.6 -0.2 1.2": ["poste"], "22.0 5.4 29.0": ["jawbreakers"], "2.5 5.6 12.1": ["metical"], "9.6 22.1 10.3": ["unfavored"], "12.8 4.0 7.5": ["maltings"], "6.9 17.0 6.0": ["stylizing"], "0.5 3.1 5.6": ["climatechange"], "12.0 23.0 25.0": ["forecastle"], "2.0 12.7 12.2": ["longe"], "6.5 2.5 10.7": ["fibril"], "5.5 15.1 19.0": ["biogeographic"], "9.2 9.3 8.2": ["leakier"], "8.2 17.6 0.8": ["exposer"], "-0.5 7.9 3.6": ["artemether"], "0.6 4.6 0.5": ["interpretational"], "2.4 8.2 4.8": ["arested"], "13.1 12.8 16.0": ["staredowns"], "-5.3 5.5 12.1": ["reapportioning"], "-0.9 -3.1 4.2": ["precertification"], "8.4 3.1 7.0": ["offe"], "7.9 3.9 9.7": ["bandroom"], "10.9 24.0 10.6": ["blockhouses"], "10.1 16.8 44.5": ["bufflehead"], "20.0 18.1 20.2": ["overclass"], "-3.2 13.2 0.7": ["toimprove"], "8.3 14.8 21.1": ["veronica"], "12.9 11.2 8.5": ["scorchingly"], "6.2 6.9 6.4": ["detatched"], "3.7 -1.5 6.3": ["leke"], "24.6 -0.2 6.6": ["supergraphic"], "3.9 4.2 7.9": ["fetlocks"], "4.9 17.2 11.9": ["flipflop"], "-2.0 11.6 6.9": ["extraverted"], "0.9 -8.6 5.7": ["eveing"], "1.9 8.9 12.6": ["aadmi"], "6.3 -1.0 3.3": ["acounts"], "1.7 9.3 8.4": ["grumping"], "8.2 4.8 23.2": ["azul"], "-1.9 4.8 -2.9": ["hadd"], "3.5 9.5 3.0": ["commen"], "6.7 -0.2 -3.0": ["thelatest"], "11.7 16.6 11.3": ["unspecialized"], "-5.6 5.1 15.9": ["pectins"], "9.3 13.8 16.9": ["snots"], "11.1 12.3 23.5": ["monotremes"], "2.1 1.9 11.0": ["topbilled"], "20.5 19.2 14.1": ["bulldust"], "-4.0 -1.4 9.1": ["cryopreserve"], "2.5 11.2 7.9": ["tomorrrow"], "-3.6 14.3 7.3": ["tov"], "5.2 27.6 5.7": ["mindgames"], "13.0 14.6 8.5": ["lampost"], "3.9 6.1 11.1": ["autoclaved"], "9.4 7.7 34.2": ["driftboat"], "18.3 12.3 21.2": ["charcoaled"], "6.7 9.6 13.4": ["phyllosilicates"], "12.4 1.7 21.0": ["falsework"], "-3.3 9.1 9.9": ["stressers"], "7.7 -4.6 18.0": ["pia"], "9.4 9.4 22.5": ["conan"], "7.2 10.8 6.8": ["cherishable"], "-3.2 -0.3 19.3": ["tups"], "9.9 8.7 24.9": ["bander"], "-1.4 1.3 6.3": ["hepatobiliary"], "-3.9 2.6 -2.9": ["listserves"], "13.5 37.0 12.8": ["nanosuit"], "4.2 12.9 7.0": ["kpg"], "0.8 5.1 3.2": ["qawwalis"], "-9.6 0.6 10.1": ["oxandrolone"], "4.1 11.5 1.9": ["privilage"], "11.0 20.6 1.1": ["incarnating"], "4.2 10.4 -1.6": ["antifamily"], "16.5 12.0 17.7": ["doof"], "3.1 23.3 0.1": ["idealisation"], "4.5 14.5 38.1": ["freestone"], "3.3 0.2 7.2": ["trak"], "4.5 11.9 4.3": ["smses"], "-1.0 10.1 6.1": ["eliminatory"], "3.2 4.6 5.4": ["interstage"], "4.5 8.5 -2.2": ["campign"], "3.0 18.6 8.5": ["ingenuousness"], "6.3 0.8 9.2": ["dittos"], "9.3 5.8 6.1": ["megasites"], "-5.3 10.5 1.8": ["ason"], "0.5 10.4 15.7": ["isos"], "16.9 0.8 5.7": ["supershow"], "-12.7 0.9 -5.7": ["inotropic"], "3.7 5.2 10.5": ["zindagi"], "11.3 -0.7 8.6": ["promenaded"], "10.3 13.5 20.3": ["fussily"], "-7.2 7.8 14.3": ["amplicons"], "14.6 12.4 7.5": ["comfiest"], "4.1 4.0 16.8": ["waysides"], "-5.3 11.2 7.2": ["interwork"], "8.5 4.9 21.7": ["suri"], "3.8 13.8 2.4": ["radiosurgical"], "11.7 10.2 15.0": ["robbie"], "-5.8 8.2 0.8": ["outvoting"], "3.2 6.4 10.0": ["lov"], "2.5 4.8 7.4": ["decortication"], "15.4 16.0 27.6": ["unhatched"], "19.4 -4.5 -1.6": ["forits"], "-2.5 -9.7 8.1": ["labiaplasty"], "-1.9 22.7 -1.2": ["incommensurable"], "-10.8 -0.1 3.3": ["expection"], "-6.4 10.4 3.8": ["clubcall"], "15.7 18.5 11.6": ["wonderingly"], "16.2 13.9 30.4": ["horsetails"], "-1.8 9.5 12.7": ["nontherapeutic"], "10.2 3.2 7.2": ["buiness"], "-0.3 9.6 6.0": ["anad"], "11.8 6.7 22.1": ["heid"], "3.8 11.6 22.3": ["farina"], "11.2 9.5 18.1": ["cowlicks"], "8.6 -2.8 9.0": ["archi"], "10.0 4.2 15.6": ["glassine"], "2.5 15.7 11.1": ["prox"], "-1.5 18.2 6.6": ["manpack"], "11.1 9.1 11.9": ["sphygmomanometer"], "10.3 4.8 8.4": ["feasable"], "4.7 2.0 12.2": ["halophytes"], "-4.2 2.3 4.4": ["cir"], "10.6 14.9 10.9": ["themselfs"], "12.6 2.4 13.7": ["seis"], "9.3 11.7 18.5": ["opsin"], "-4.4 17.0 7.9": ["nefesh"], "15.0 15.9 30.3": ["springtails"], "16.8 13.5 18.3": ["companionably"], "10.1 2.4 2.8": ["chlorofluorocarbon"], "-5.9 10.8 -0.5": ["oglu"], "6.3 21.1 9.4": ["amongs"], "12.3 11.6 15.6": ["bragger"], "14.6 7.9 10.8": ["tesco"], "5.4 7.3 18.3": ["scot"], "6.8 15.3 7.2": ["squee"], "-9.2 12.8 6.5": ["lieved"], "21.7 6.9 20.3": ["aurochs"], "1.6 5.2 1.1": ["aspherical"], "8.3 10.9 16.9": ["murse"], "10.8 15.2 47.3": ["pigfish"], "7.5 11.0 14.8": ["wakeskaters"], "18.9 6.1 10.4": ["sheathes"], "5.4 8.4 10.4": ["oma"], "-6.7 4.0 15.2": ["meron"], "5.4 -4.3 -8.1": ["debute"], "-6.0 16.0 12.6": ["relapsers"], "5.5 7.9 5.2": ["rewinder"], "3.0 7.8 0.7": ["hypersonics"], "-10.8 1.0 3.8": ["elgible"], "7.1 4.5 1.0": ["hacia"], "11.9 10.5 12.4": ["loverly"], "9.9 1.3 12.1": ["jerricans"], "-0.6 0.2 7.7": ["illico"], "15.6 13.6 35.7": ["overwinters"], "9.1 3.3 2.9": ["zich"], "4.4 9.2 18.0": ["chamfer"], "-1.3 1.6 2.0": ["diaphragmatic"], "16.7 9.4 4.7": ["megarich"], "16.1 3.3 11.9": ["ubs"], "3.1 12.1 2.9": ["thereis"], "-1.4 5.5 12.3": ["compoundable"], "5.4 2.6 17.3": ["slaughterings"], "16.0 7.1 18.5": ["hawthorne"], "6.0 7.1 11.0": ["clockmakers"], "-0.4 -3.2 6.8": ["cisapride"], "2.4 -1.3 12.2": ["infills"], "3.5 12.1 14.4": ["nooky"], "6.1 -3.1 9.6": ["xanthan"], "17.0 14.6 18.6": ["klepto"], "7.6 5.1 10.3": ["palaeo"], "-9.2 2.5 4.3": ["conclusiveness"], "14.4 16.0 38.5": ["auklets"], "12.9 7.1 10.3": ["coffeepots"], "10.0 5.2 18.0": ["planche"], "7.5 5.1 26.8": ["redcurrant"], "4.7 12.7 3.9": ["redacts"], "3.8 4.4 15.2": ["fid"], "16.5 23.8 7.6": ["yappers"], "-2.3 1.4 9.6": ["parsonages"], "6.0 18.7 21.4": ["malaprop"], "11.7 9.4 33.9": ["clafoutis"], "4.1 6.8 13.1": ["clint"], "18.6 18.1 19.2": ["smushing"], "5.1 8.9 6.9": ["sickouts"], "16.3 9.7 17.9": ["aeroshell"], "6.7 25.2 5.8": ["shrillest"], "5.6 11.2 4.9": ["exchequers"], "-5.3 3.5 2.9": ["pamidronate"], "11.0 4.5 20.9": ["greene"], "10.1 7.2 29.1": ["alstroemeria"], "8.5 15.7 5.0": ["governmet"], "4.8 20.7 1.6": ["opposer"], "17.7 4.4 12.9": ["polymethylmethacrylate"], "3.3 19.2 3.2": ["engrosses"], "4.6 0.3 9.8": ["cagefest"], "16.0 16.1 19.9": ["skittishly"], "-9.3 10.0 9.4": ["reteaching"], "6.3 11.3 9.5": ["motesanib"], "2.8 6.3 4.4": ["upfitting"], "5.9 0.9 13.5": ["phyllite"], "-6.5 19.3 8.0": ["governates"], "-3.5 -0.3 -7.5": ["studing"], "-6.0 2.8 4.3": ["edn"], "1.2 6.1 4.8": ["ruboxistaurin"], "11.4 9.4 14.9": ["pointillistic"], "19.6 29.8 3.7": ["cyberspies"], "10.7 4.7 5.0": ["idc"], "11.9 6.2 20.1": ["bargoers"], "7.1 7.3 10.5": ["minibreak"], "6.8 -2.1 9.1": ["plasticiser"], "-1.2 2.8 4.0": ["dalfampridine"], "18.8 -3.3 13.4": ["seco"], "16.4 13.1 14.5": ["distend"], "11.2 6.2 11.6": ["electrostatically"], "-0.2 9.6 16.4": ["fibresand"], "22.3 18.3 14.5": ["deadpool"], "15.3 22.5 13.6": ["hoverboards"], "7.1 32.7 6.6": ["praetorian"], "-2.6 22.4 4.5": ["kinsfolk"], "1.1 -2.3 -1.2": ["intercarrier"], "1.5 0.6 14.4": ["cov"], "16.2 5.3 6.1": ["tronic"], "1.3 11.6 8.0": ["yeahs"], "21.1 2.5 17.7": ["cocos"], "2.0 8.9 12.0": ["bieng"], "0.4 11.4 5.3": ["elastase"], "11.1 2.4 6.4": ["cremator"], "8.1 11.4 45.8": ["surfcasting"], "13.0 15.8 19.6": ["gigaton"], "-3.9 2.9 3.4": ["whiel"], "13.5 14.2 8.0": ["wonkiness"], "7.9 11.1 16.1": ["yohimbine"], "13.7 17.6 5.0": ["survelliance"], "10.3 16.9 15.8": ["squishiness"], "-2.1 10.1 8.7": ["equilibration"], "2.2 1.6 9.8": ["yad"], "5.9 2.8 9.6": ["lawbooks"], "9.4 10.0 13.3": ["stealin"], "5.3 21.8 2.6": ["mubarak"], "3.7 8.1 3.5": ["newsier"], "4.4 16.2 8.0": ["convolute"], "12.2 16.4 15.2": ["greentop"], "5.5 -4.2 7.2": ["gbps"], "5.6 10.4 16.4": ["delaminating"], "3.9 10.4 12.6": ["oxidisation"], "-0.8 10.2 7.2": ["rediscoveries"], "3.7 2.8 0.3": ["tsun"], "2.6 -0.3 4.4": ["produ"], "9.3 21.7 10.3": ["inkblots"], "13.5 17.8 14.3": ["infantilization"], "7.8 10.9 22.0": ["portaged"], "7.4 11.7 7.8": ["embolus"], "4.6 10.7 28.5": ["ecoli"], "2.2 6.7 9.4": ["solubilization"], "-4.0 5.4 2.5": ["petechiae"], "19.0 10.5 16.4": ["shoulderpads"], "15.5 11.0 9.9": ["nanopillars"], "13.8 3.5 13.9": ["justa"], "-0.0 19.8 11.5": ["housetraining"], "2.4 6.5 4.9": ["readbacks"], "9.2 4.3 10.6": ["outliner"], "14.5 9.1 12.0": ["superclubs"], "4.7 -9.9 0.5": ["livestreamed"], "9.1 14.5 18.2": ["declension"], "2.9 5.2 17.2": ["moog"], "10.8 21.1 21.9": ["parasitize"], "2.0 18.8 12.5": ["keyset"], "14.7 5.3 6.2": ["otoscope"], "4.3 22.8 12.7": ["mindbender"], "19.3 9.3 13.4": ["ciggy"], "10.9 10.1 11.7": ["oversaturate"], "-4.9 -0.6 5.6": ["grayshirted"], "1.4 -2.0 27.5": ["oilmeals"], "9.2 6.3 18.8": ["nong"], "9.8 12.6 8.3": ["blubbed"], "-2.2 8.2 13.3": ["kagawad"], "13.2 11.7 18.0": ["senorita"], "10.0 3.5 31.2": ["skimboard"], "15.5 13.9 4.8": ["evergrowing"], "13.8 15.2 19.3": ["squeegeed"], "9.1 14.2 7.9": ["unlatching"], "1.4 44.2 2.7": ["strongpoints"], "12.4 17.6 23.9": ["caracal"], "3.0 6.6 13.7": ["guestworker"], "5.7 13.3 14.7": ["esse"], "5.1 6.6 12.6": ["flexural"], "18.5 10.4 9.1": ["ornamenting"], "9.4 7.4 1.9": ["resynchronize"], "4.6 22.4 11.4": ["empath"], "5.2 15.1 4.4": ["censorial"], "1.9 13.8 5.1": ["desperatly"], "12.0 7.2 4.3": ["imediately"], "15.7 16.2 4.9": ["somnambulist"], "13.4 7.7 15.0": ["refolded"], "9.6 5.2 15.0": ["dossing"], "13.3 8.0 -7.9": ["claimes"], "-2.6 3.5 3.9": ["titres"], "-5.2 7.5 2.8": ["treadwear"], "-3.9 -2.5 14.9": ["bootcut"], "16.0 9.0 10.1": ["mirasol"], "6.8 15.3 24.3": ["yola"], "-6.9 5.7 3.0": ["ponencia"], "6.6 10.3 12.5": ["poshness"], "13.3 31.1 5.5": ["boobytraps"], "5.2 6.5 6.5": ["voce"], "-4.1 -3.4 12.3": ["occ"], "7.4 -2.1 0.7": ["exhbition"], "5.6 4.0 18.4": ["heatspreaders"], "2.8 9.0 10.6": ["quam"], "19.4 19.7 9.8": ["dorkiest"], "3.3 18.2 8.6": ["relock"], "12.3 6.0 6.2": ["hij"], "4.9 30.5 3.2": ["dreadfulness"], "-6.7 12.5 3.9": ["imambargahs"], "-9.7 6.6 2.7": ["positons"], "7.2 15.9 4.1": ["duststorm"], "22.8 3.3 4.8": ["abacuses"], "-0.2 2.8 6.0": ["sacco"], "17.1 0.5 6.4": ["mems"], "10.1 7.5 18.4": ["fixup"], "0.7 12.0 3.2": ["photorealist"], "13.3 10.3 20.6": ["swather"], "4.6 5.9 -4.7": ["allof"], "13.1 0.5 32.8": ["sopapillas"], "10.3 10.6 20.6": ["lakebeds"], "-10.3 10.2 -2.8": ["rabbonim"], "8.1 7.1 25.1": ["yorkie"], "5.5 7.0 -1.9": ["tokeep"], "12.0 9.2 17.2": ["overwrap"], "15.3 10.6 26.4": ["buckteeth"], "10.1 21.0 16.1": ["doge"], "11.0 5.5 5.1": ["dashikis"], "13.3 15.2 12.3": ["fretfully"], "15.0 13.2 13.9": ["adorability"], "11.0 11.4 11.9": ["infantilised"], "13.9 11.7 17.0": ["mechanizing"], "-4.0 11.0 1.2": ["procurators"], "10.6 7.3 36.3": ["nutella"], "22.5 13.4 44.7": ["gastropod"], "11.5 11.9 10.6": ["decommissions"], "1.0 4.2 19.6": ["follistatin"], "3.0 14.0 5.2": ["politer"], "6.8 8.8 3.1": ["arcseconds"], "8.8 26.9 6.2": ["diffract"], "6.6 5.8 -3.1": ["influentially"], "16.1 13.9 8.7": ["grimiest"], "10.7 6.9 18.0": ["idyllically"], "8.7 10.0 18.9": ["cali"], "22.2 7.3 3.4": ["billionare"], "15.9 11.4 7.2": ["necklaced"], "9.0 -0.2 16.2": ["capstones"], "-3.9 13.7 8.9": ["microvesicles", "flabbergasts"], "11.8 2.6 14.7": ["kvass"], "3.2 10.1 9.7": ["institutionals"], "7.7 15.2 5.0": ["supernode"], "15.1 12.3 15.1": ["canefields"], "5.7 11.2 4.6": ["bevasiranib"], "13.0 2.6 5.1": ["utilty"], "9.3 7.0 6.8": ["calles"], "21.3 10.5 8.3": ["footling"], "8.3 -1.6 -0.5": ["healthcheck"], "15.7 18.9 17.2": ["brainlessly"], "-0.2 8.1 5.6": ["halides"], "22.6 22.4 21.5": ["bludger"], "7.6 13.5 18.1": ["bitchery"], "-1.3 8.6 4.0": ["gharanas"], "9.4 16.1 10.8": ["everymen"], "8.0 12.7 5.3": ["buit"], "5.5 8.0 27.2": ["kugels"], "4.6 9.7 3.2": ["entitites"], "-11.6 0.2 0.5": ["toensure"], "-7.5 14.2 3.1": ["naik"], "13.8 21.5 9.5": ["landlordism"], "18.0 10.2 32.9": ["bouy"], "5.9 2.1 7.2": ["pena"], "14.2 23.7 7.0": ["tunnellers"], "0.6 8.6 4.0": ["denervation"], "15.0 6.9 8.9": ["brooming"], "13.8 5.3 16.3": ["fenland"], "1.4 -4.1 17.0": ["vealers"], "16.0 27.9 13.5": ["enslavers"], "8.6 9.6 6.0": ["photoactive"], "11.0 8.6 26.9": ["cardamon"], "-10.2 -2.3 10.5": ["twoweek"], "20.1 10.7 32.2": ["kapok"], "16.4 8.1 27.7": ["megalodon"], "13.2 28.7 7.8": ["armours"], "1.7 2.8 29.9": ["bellini"], "15.1 5.5 9.2": ["houselights"], "-0.5 9.9 4.9": ["mispelled"], "-1.6 10.7 2.5": ["resect"], "9.6 12.4 15.5": ["auteurist"], "17.3 6.8 10.8": ["luggable"], "14.1 13.7 10.8": ["lithely"], "7.7 18.9 9.0": ["weirds"], "20.6 17.4 18.9": ["casements"], "10.2 21.2 13.2": ["suckitude"], "-6.2 1.7 14.8": ["nonrenewals"], "12.5 13.5 17.4": ["whinnied"], "9.4 -4.0 4.9": ["cremators"], "6.3 6.5 8.4": ["anteriorly"], "-3.1 4.9 1.0": ["ofloxacin"], "2.5 -1.4 11.0": ["capsulized"], "-0.0 0.9 -1.7": ["isopropyl"], "1.1 14.1 3.5": ["nosetackle"], "12.9 8.0 12.4": ["trunkload"], "14.4 22.1 8.5": ["quadricopter"], "7.5 15.8 13.5": ["moroseness"], "6.7 19.2 10.7": ["youcan"], "9.2 12.0 4.8": ["spectrogram"], "9.4 15.6 3.6": ["heis"], "0.8 19.8 12.5": ["nisei"], "0.9 2.9 16.0": ["walters"], "-0.7 10.8 3.4": ["halons"], "1.1 5.5 13.8": ["wieght"], "9.2 18.6 9.2": ["straigh"], "5.3 13.4 2.6": ["derelictions"], "-2.8 4.1 -3.4": ["critisized"], "9.9 23.0 11.3": ["gunfighting"], "11.1 4.8 11.5": ["subbies"], "7.8 -0.6 17.4": ["chiu"], "0.6 14.1 3.0": ["oratories"], "6.5 13.0 12.3": ["reblooming"], "13.2 13.2 9.6": ["multisyllabic"], "11.3 14.5 16.6": ["drippers"], "7.1 -1.8 10.5": ["pataca"], "-0.1 3.5 9.5": ["mcft"], "14.2 2.3 1.7": ["travelators"], "22.2 -1.1 13.9": ["augustus"], "6.8 7.1 3.8": ["xs"], "0.4 2.8 20.8": ["greige"], "16.6 13.7 2.4": ["lauching"], "6.9 9.3 8.5": ["arthouses"], "1.0 5.0 4.7": ["varistors"], "8.2 19.9 12.2": ["australians"], "5.9 13.0 3.9": ["spellbinder"], "12.1 4.2 15.7": ["fixe"], "19.6 7.5 4.6": ["labyrinthian"], "2.6 0.2 2.0": ["nullhe"], "6.5 10.1 13.9": ["watercolourist"], "4.0 10.5 5.7": ["mades"], "2.6 10.9 8.1": ["nondrinker"], "5.5 9.0 14.8": ["rufiyaa"], "6.7 3.4 14.2": ["caro"], "2.6 26.5 15.1": ["elementally"], "1.6 11.0 13.9": ["aapko"], "10.5 13.7 10.9": ["donnybrooks"], "3.1 11.6 7.0": ["sacrified"], "1.6 0.2 -0.1": ["psychostimulant"], "5.7 15.7 23.1": ["bwoy"], "4.1 -0.4 12.3": ["packagings"], "-2.7 7.3 11.5": ["npr"], "9.1 8.0 31.5": ["cascarones"], "6.2 4.0 15.5": ["tephra"], "11.5 15.4 19.5": ["stfu"], "6.6 3.0 16.6": ["lowveld"], "-6.5 -1.1 4.6": ["ibandronate"], "-3.2 16.3 5.5": ["graydon"], "4.5 10.3 7.6": ["colorfulness"], "2.1 13.7 18.1": ["jiu"], "6.2 8.8 12.1": ["cela"], "-3.1 21.3 9.7": ["adamantanes"], "9.2 11.4 9.5": ["bizjet"], "1.8 6.1 10.9": ["ovules"], "7.3 1.9 13.8": ["strappers"], "7.9 13.9 27.0": ["siskins"], "5.1 19.0 12.9": ["insatiability"], "-1.4 21.6 -5.0": ["havaldar"], "1.0 9.6 11.5": ["magnetospheric"], "12.7 20.1 16.4": ["mofos"], "4.1 9.6 13.1": ["countryish"], "2.2 4.0 20.9": ["bab"], "9.9 6.6 28.4": ["shish"], "-0.5 8.7 12.2": ["hatha"], "-1.1 11.9 -2.8": ["reportings"], "19.3 23.0 18.2": ["quailed"], "20.1 -3.3 7.5": ["cheapish"], "9.1 12.9 13.6": ["roofie"], "6.8 13.0 6.4": ["humidifying"], "-3.7 8.6 0.5": ["understandability"], "-3.3 5.7 8.8": ["toteplacepot"], "-8.5 1.6 6.7": ["batswoman"], "24.8 5.9 14.4": ["lightposts"], "5.5 7.1 20.2": ["snowmachiner"], "12.8 19.3 17.1": ["polecats"], "-1.4 9.1 9.3": ["relly"], "16.6 13.9 23.3": ["mainsails"], "8.8 -3.8 17.7": ["bev"], "14.3 25.3 2.0": ["poweful"], "22.0 17.7 17.9": ["tetris"], "5.7 33.5 7.9": ["defenselessness"], "-0.6 8.6 11.4": ["thermoregulatory"], "-8.2 8.0 5.7": ["penname"], "17.3 9.5 19.4": ["lolloping"], "2.6 18.6 10.0": ["hypos"], "18.1 5.0 31.1": ["ichthyosaurs"], "4.1 11.6 6.1": ["housebreakers"], "11.5 5.5 24.8": ["turquoises"], "9.5 2.7 14.1": ["shoppin"], "4.2 11.2 22.4": ["livestocks"], "10.7 18.7 21.5": ["anklelock"], "1.5 22.3 5.9": ["introspecting"], "5.7 5.2 -2.0": ["playlisting"], "13.4 -1.6 0.6": ["toits"], "11.3 11.8 14.8": ["oblate"], "-2.2 -1.2 5.6": ["hymens"], "6.5 10.4 19.7": ["brambly"], "-1.6 12.5 7.8": ["unformatted"], "12.2 9.1 7.0": ["adhl"], "3.8 -2.5 23.5": ["cheong"], "17.3 12.3 30.7": ["weiners"], "4.4 11.5 13.1": ["sharmajunior"], "2.5 9.2 17.2": ["luma"], "-1.4 10.8 3.3": ["knowledges"], "4.2 6.6 5.9": ["competeing"], "-2.7 9.8 5.0": ["forbearances"], "-1.5 14.3 10.2": ["nociceptors"], "15.9 13.5 7.2": ["transfixes"], "6.8 4.7 7.5": ["midsong", "conqueroo"], "5.1 10.5 15.9": ["collaging"], "1.6 4.0 10.8": ["mouzas"], "5.2 12.1 11.9": ["improvidently"], "2.5 9.7 12.3": ["affianced"], "3.3 17.2 5.7": ["sophistic"], "1.5 5.0 16.7": ["gani"], "-6.3 0.2 6.2": ["pomalidomide"], "17.3 15.7 41.2": ["yabby"], "-1.1 1.0 0.6": ["thyristors"], "6.4 11.5 8.2": ["sportives"], "6.9 8.3 7.2": ["microreactors"], "5.5 23.4 8.6": ["beleaguer"], "7.8 9.3 14.8": ["looove"], "11.8 -0.4 21.6": ["gladiola"], "7.4 26.6 7.4": ["metastasise"], "2.1 8.5 10.7": ["sketcher"], "15.1 9.3 18.6": ["yummier"], "4.5 10.0 23.3": ["pizzaiolo"], "8.6 7.9 15.0": ["vmf"], "0.2 -2.7 9.7": ["fareboxes"], "7.7 15.0 1.4": ["sutler"], "2.3 4.7 12.4": ["potability"], "21.1 0.9 10.4": ["uncrated"], "0.4 0.5 1.7": ["biaxial"], "7.8 16.2 15.7": ["pantheons"], "9.9 17.1 9.7": ["pluperfect"], "18.5 9.8 23.5": ["creamsicle"], "-1.9 13.2 4.0": ["perfer"], "5.9 19.0 13.4": ["bhadralok"], "1.0 6.1 27.8": ["gosht"], "5.6 2.2 8.9": ["snitty"], "9.2 10.9 11.8": ["proxying"], "14.6 24.7 19.2": ["everydayness"], "9.2 8.8 15.9": ["hud"], "11.7 8.4 4.8": ["paster"], "9.3 3.5 7.6": ["powercut"], "-0.8 13.8 9.3": ["transliterations"], "-3.8 1.6 9.6": ["residentials"], "4.7 5.7 19.7": ["betelnut"], "5.8 -3.1 7.9": ["annualy"], "8.1 18.7 3.3": ["pysche"], "0.1 2.9 -3.7": ["finshing"], "-2.7 12.6 15.8": ["psuedoephedrine"], "12.2 9.9 22.1": ["polonaise"], "10.1 6.7 9.7": ["biofiltration"], "0.2 6.0 16.0": ["inde"], "11.2 -1.2 15.7": ["lakeview"], "16.1 13.1 15.1": ["hooha"], "1.7 -10.1 2.1": ["directorgeneral"], "-7.6 1.1 4.4": ["patristic"], "8.5 26.4 19.8": ["shogunate"], "-1.4 30.8 13.7": ["terps"], "1.3 2.4 1.2": ["varespladib"], "13.7 8.7 21.2": ["dalmatians"], "8.9 10.0 13.3": ["blacktops"], "-0.6 1.9 8.5": ["chelated"], "6.3 8.8 8.0": ["freebasing"], "-11.4 14.6 6.1": ["ahadith"], "-0.6 31.4 13.6": ["immanence"], "5.7 2.0 4.0": ["nextstep"], "10.8 20.7 11.3": ["tutelary"], "12.0 15.8 11.3": ["moran"], "20.2 -1.0 5.4": ["fastestgrowing"], "4.0 9.7 5.9": ["tweakable"], "-8.2 11.0 2.1": ["preferenced"], "5.2 15.3 16.3": ["sensitives"], "8.5 22.0 19.5": ["throwable"], "-2.8 13.8 8.1": ["papabili"], "7.3 16.6 7.6": ["somnambulistic"], "17.3 11.3 8.0": ["plasticy"], "19.3 11.4 26.2": ["weta"], "-0.6 20.1 6.5": ["precipitant"], "14.7 18.9 11.7": ["grrrr"], "13.1 7.3 11.2": ["taichi"], "5.4 23.9 10.8": ["unhistorical"], "3.9 14.3 2.7": ["shamash"], "4.4 4.1 15.8": ["copperplate"], "3.6 20.2 6.4": ["mistruth"], "-2.0 12.9 -3.6": ["simcard"], "12.1 13.5 21.3": ["gymnosperms"], "3.7 4.2 5.1": ["petrophysics"], "2.8 8.4 2.6": ["collocations"], "-4.1 1.7 10.9": ["posaconazole"], "6.3 7.0 18.9": ["tetraploid"], "12.1 20.4 15.4": ["belayer"], "-3.5 10.6 -2.4": ["adde"], "10.3 6.9 10.8": ["pater"], "9.5 5.3 17.9": ["underlaid"], "6.2 11.9 4.5": ["inflexion"], "16.1 0.8 21.8": ["megaport"], "9.0 39.4 8.5": ["groundfire"], "3.8 0.3 30.4": ["rellenos"], "14.2 4.3 39.6": ["pimiento"], "5.3 20.6 5.1": ["fatuousness"], "7.2 0.8 7.3": ["microbudget"], "14.0 7.9 5.8": ["descrambling"], "11.6 9.6 23.7": ["pelargonium"], "9.5 9.8 5.0": ["railheads"], "15.3 15.6 24.5": ["rhodies"], "12.8 10.4 22.2": ["afterburn"], "2.0 1.7 7.4": ["boxsets"], "7.1 0.7 2.4": ["entirity"], "11.1 16.3 2.0": ["firecrotch"], "5.7 11.6 13.5": ["headgates"], "-0.8 11.9 27.6": ["pilafs"], "13.3 0.0 14.5": ["crotchet"], "6.7 3.1 9.8": ["overprovision"], "8.4 9.5 34.8": ["sora"], "4.6 -3.1 -2.3": ["nati"], "-3.2 13.5 31.8": ["cervids"], "10.1 23.2 22.5": ["faery"], "8.0 11.5 5.3": ["decarbonised"], "15.0 5.0 8.0": ["revivifying"], "4.9 17.2 2.8": ["advantaging"], "8.0 8.4 27.0": ["upma"], "-0.4 13.0 12.6": ["weathercasts"], "2.9 12.5 13.0": ["precints"], "10.1 6.9 8.4": ["springier"], "-2.5 2.7 14.1": ["amylose"], "2.7 2.6 9.7": ["appraoch"], "-0.4 1.3 -0.1": ["rity"], "14.5 3.8 16.1": ["shoulderless"], "18.7 4.7 14.0": ["karoake"], "0.1 2.9 1.5": ["pictoral"], "5.0 11.5 35.8": ["wigeons"], "14.3 17.5 9.7": ["outfoxes"], "12.9 13.1 31.4": ["nightjar"], "15.3 -0.2 4.3": ["bilks"], "7.9 11.6 15.7": ["frostiest"], "0.3 11.7 6.7": ["definers"], "-3.8 4.5 3.3": ["splenomegaly"], "8.9 2.7 5.6": ["globale"], "13.9 13.1 16.7": ["yatch"], "-2.4 3.6 8.5": ["hometrack"], "11.6 6.3 12.1": ["automat"], "3.9 -1.7 -1.4": ["hugin"], "6.3 0.8 8.7": ["pgms"], "8.7 12.9 13.5": ["charpoy"], "12.2 4.4 16.6": ["troubador"], "11.0 11.6 9.4": ["pixelate"], "0.8 12.0 5.5": ["sparce"], "-3.3 3.0 3.6": ["woolhandling"], "11.3 10.9 10.8": ["buffetted"], "15.7 4.2 30.5": ["daschund"], "4.3 17.7 10.4": ["gunnin"], "6.4 7.5 7.3": ["benefactress"], "5.3 18.0 9.5": ["minutae"], "-2.2 6.3 -7.5": ["leade"], "10.1 4.3 14.2": ["irreverant"], "9.1 2.3 8.5": ["aon"], "-4.3 6.3 8.0": ["norming"], "-2.3 4.2 3.1": ["trackability"], "2.3 1.9 8.8": ["dyads"], "3.6 12.2 12.3": ["alpinism"], "16.9 23.1 14.9": ["destines"], "-4.6 10.8 -2.9": ["accuseds"], "8.5 14.1 11.3": ["mavs"], "9.5 0.6 5.4": ["starmaking"], "10.1 -5.4 4.4": ["oggi"], "2.5 -0.3 5.4": ["scf"], "-5.5 22.4 -2.9": ["instrumentalized"], "0.4 23.6 10.8": ["retrogressing"], "8.2 3.2 22.8": ["nucleated"], "11.6 6.5 11.1": ["chicness"], "0.4 7.8 -2.3": ["flt"], "2.4 18.1 15.9": ["popish"], "4.2 14.7 3.7": ["diference"], "15.0 15.2 3.4": ["superspeed"], "19.3 6.0 23.6": ["dreamcatchers"], "15.2 11.5 16.9": ["dullsville"], "5.1 10.4 8.8": ["racecaller"], "0.1 -0.7 10.2": ["polytechs"], "3.1 9.0 15.9": ["bellybuttons"], "-1.1 6.6 7.5": ["osteoarthritic"], "8.8 24.1 4.5": ["supinely"], "13.4 22.1 15.4": ["frakking"], "15.0 10.1 16.7": ["corrugation"], "8.5 9.6 17.7": ["quittin"], "8.9 -2.1 15.8": ["platers"], "5.5 14.9 11.0": ["hosses"], "2.5 14.1 12.8": ["giggler"], "4.1 16.9 20.4": ["mournfulness"], "7.5 1.6 19.2": ["denise"], "7.1 2.7 30.4": ["cordyceps"], "3.0 5.8 13.5": ["faming"], "10.3 17.1 17.5": ["expeditioners"], "11.1 9.5 7.4": ["hus"], "2.4 20.0 8.7": ["airtanker"], "-1.5 15.9 8.6": ["papillomas"], "8.7 16.6 8.7": ["tuts"], "6.9 6.7 1.8": ["oversaturating"], "15.9 -1.6 12.4": ["densified"], "-2.8 5.1 2.0": ["eof"], "22.5 7.7 15.2": ["hypermart"], "2.6 10.0 8.2": ["excitotoxicity"], "1.9 5.9 8.1": ["scorefest"], "7.6 9.1 16.5": ["espadrille"], "15.0 -4.0 2.9": ["fiberoptics"], "14.6 26.9 34.9": ["diamondback"], "7.8 6.8 13.6": ["forehander"], "5.5 15.2 13.1": ["noloyalisti"], "7.1 12.9 13.0": ["kiasu"], "8.4 5.5 25.7": ["gunite"], "-3.1 10.5 1.7": ["keyholders"], "-1.7 5.3 0.0": ["diastole"], "4.2 6.9 7.1": ["limning"], "6.6 15.1 4.5": ["straightly"], "6.0 13.2 12.2": ["lockpicking"], "5.6 11.2 12.9": ["wena"], "-2.7 6.9 -0.2": ["comittment"], "0.9 11.3 11.7": ["explosivity"], "7.1 4.9 5.3": ["worringly"], "4.0 7.5 4.0": ["followin"], "9.5 -0.1 8.5": ["sturm"], "8.7 18.2 11.1": ["masochistically"], "5.9 3.5 6.9": ["toolbelt"], "4.5 4.1 3.4": ["mindestens"], "5.4 -2.9 3.5": ["sugery"], "1.4 17.3 29.8": ["phoebes"], "9.7 14.6 9.9": ["leechers"], "9.2 1.0 22.8": ["diamantes"], "4.4 13.8 15.4": ["taijiquan"], "2.6 1.2 6.5": ["redoes"], "1.7 14.5 18.0": ["farangs"], "-4.4 12.4 13.8": ["azole"], "6.9 10.5 2.4": ["wireman"], "10.4 0.5 13.7": ["chapeaus"], "4.0 20.4 6.4": ["enlightment"], "0.2 14.5 14.7": ["gazundering"], "6.8 12.3 2.1": ["continu"], "3.5 10.0 3.4": ["limitedly"], "5.0 -5.1 2.3": ["classis"], "10.3 -2.3 22.6": ["pista"], "18.4 7.3 20.3": ["knackers"], "6.2 24.3 8.2": ["overpursuing"], "4.3 9.0 16.2": ["mons"], "3.5 17.1 4.9": ["bcause"], "4.5 6.6 10.4": ["retun"], "4.7 4.0 11.5": ["nuit"], "0.9 9.1 -1.5": ["todevelop"], "-4.5 13.9 0.9": ["tuttomercatoweb"], "-1.1 9.8 10.4": ["archness"], "16.6 -0.1 0.0": ["visualizers"], "-3.9 14.5 10.4": ["protagonistic"], "3.2 0.8 24.2": ["kopi"], "19.2 10.2 16.0": ["goggling"], "20.8 2.6 11.8": ["airbed"], "1.5 13.3 16.3": ["goe"], "-2.6 15.0 3.1": ["maryada"], "-0.7 14.0 9.0": ["tweek"], "5.7 6.6 9.3": ["brail"], "13.8 6.8 19.0": ["bevies"], "10.2 15.5 23.0": ["cotto"], "20.4 10.3 13.4": ["maskers"], "-6.7 11.5 5.1": ["paresis"], "14.0 -1.3 -0.6": ["fuseproject"], "-2.6 6.1 13.7": ["babae"], "10.4 13.3 27.1": ["ajuga"], "-2.1 3.1 -0.7": ["monographic"], "6.2 -3.0 6.5": ["yars"], "-6.2 1.3 0.4": ["gradate"], "-4.4 13.0 17.1": ["kuleana"], "-2.6 5.0 2.4": ["interalia"], "10.1 2.8 7.6": ["droping"], "7.3 3.2 16.0": ["moisturises"], "13.5 2.3 6.3": ["realtones"], "13.4 28.4 11.0": ["lessers"], "5.5 14.5 6.7": ["sibilance"], "12.0 8.8 19.4": ["moonflower"], "6.1 7.8 -0.6": ["locative"], "4.5 1.4 3.4": ["ihren"], "-7.3 8.6 -1.9": ["antineoplastic"], "-2.6 5.3 30.7": ["salinities"], "4.9 4.0 -3.7": ["forfour"], "10.0 7.2 13.6": ["vai"], "1.6 16.8 6.3": ["tradgedy"], "-4.0 5.5 15.1": ["behavoir"], "5.9 7.4 0.5": ["multistarrer"], "-0.2 11.1 6.7": ["sexi"], "0.4 15.3 11.4": ["scots"], "6.5 2.3 13.1": ["meltshop"], "-4.0 -7.3 -3.3": ["qualfied"], "2.7 0.5 0.1": ["professionnel"], "4.3 13.0 19.2": ["centerfire"], "7.9 -2.8 -4.2": ["todeliver"], "10.1 22.3 19.3": ["rapiers"], "-3.2 24.6 8.2": ["civilities"], "2.6 7.0 3.6": ["tearily"], "12.2 7.9 2.4": ["jubiliant"], "1.5 9.4 7.0": ["rearfoot"], "11.8 14.0 37.6": ["fritillaries"], "-7.9 8.7 0.2": ["fulminant"], "12.2 20.9 2.0": ["guiles"], "4.6 13.9 15.3": ["meboard"], "-1.9 6.9 -0.8": ["throughoutthe"], "-0.9 6.8 2.6": ["paracrine"], "25.5 5.9 12.4": ["vertiginously"], "-3.1 6.1 -2.7": ["frey"], "20.4 9.3 35.8": ["borealis"], "1.4 20.2 4.5": ["shrapnels"], "3.3 10.8 15.6": ["reyes"], "10.7 8.4 7.9": ["radiometers"], "0.2 6.0 5.0": ["keratinocyte"], "4.5 -5.0 7.9": ["lexus"], "3.7 11.7 15.2": ["unfragmented"], "17.2 11.3 21.4": ["motorless"], "1.0 8.5 5.1": ["felodipine"], "-4.6 15.6 12.2": ["indecisions"], "26.0 10.0 25.8": ["dookie"], "6.2 19.7 13.3": ["firsters"], "-8.7 3.6 17.8": ["mancozeb"], "10.0 12.6 38.3": ["slaws"], "5.3 8.9 8.5": ["vitalized"], "15.9 5.1 17.4": ["faddy"], "3.7 7.9 15.4": ["hyphenates"], "3.8 5.5 5.2": ["gyaan"], "-1.8 10.5 6.0": ["nonoccurrence"], "4.6 15.9 10.5": ["capi"], "7.7 19.1 14.7": ["brutishly"], "6.6 5.9 12.3": ["vajayjay"], "-0.3 24.6 7.3": ["taqwa"], "22.5 18.5 17.9": ["mandrake"], "13.8 1.3 2.1": ["bootees"], "-5.0 21.3 5.5": ["nuancing"], "20.0 15.6 2.2": ["ionizes"], "8.0 7.1 15.8": ["erik"], "5.9 -0.5 -2.4": ["caled"], "6.6 7.0 30.6": ["bilberries"], "-0.4 1.5 5.6": ["housemen"], "3.3 4.4 6.5": ["draughtsmen"], "-4.6 12.2 4.6": ["nonactors"], "17.9 23.0 13.3": ["flamer"], "-6.5 11.2 9.8": ["immunocompetent"], "1.4 4.1 11.1": ["milimetres"], "12.0 -0.9 18.1": ["tums"], "8.2 12.7 12.0": ["gloveside"], "-0.4 21.7 12.2": ["interservice"], "-2.2 16.2 -6.3": ["annunciated"], "13.2 4.9 35.4": ["fishiness"], "0.0 3.9 7.8": ["cbi"], "-11.5 21.0 3.5": ["paygrade"], "17.5 8.7 7.1": ["preroll"], "7.7 10.3 1.4": ["datamining"], "11.7 11.1 -0.2": ["germiest"], "11.2 3.0 12.6": ["framerails", "mostra"], "0.1 0.5 5.2": ["bicommunal"], "13.6 18.9 25.3": ["treeing"], "3.7 11.7 6.6": ["speechify"], "1.1 6.0 -0.9": ["tripwolf"], "2.4 10.4 4.9": ["outbrake"], "12.5 14.9 8.2": ["jefe"], "-4.1 28.9 5.3": ["bondages"], "-0.6 15.5 23.7": ["crustiness"], "14.0 12.7 -3.5": ["spreaded"], "1.3 8.3 13.9": ["hoppier"], "2.9 6.5 6.3": ["prefetching"], "6.7 7.0 10.1": ["vivaciously"], "6.5 6.8 4.4": ["gujarat"], "8.3 -4.8 9.9": ["necitumumab"], "-10.2 21.6 3.8": ["civilianization"], "-4.6 -3.6 19.9": ["camelid"], "1.7 14.1 10.8": ["jared"], "8.2 11.4 8.5": ["castro"], "16.1 4.3 13.8": ["pantomine"], "4.8 19.7 14.7": ["saju"], "1.4 -5.3 9.7": ["lig"], "9.6 19.6 13.1": ["concupiscence"], "7.7 11.4 12.0": ["edgar"], "5.7 12.6 13.2": ["fumblerooski"], "8.9 14.0 8.9": ["italicised"], "5.6 13.1 7.5": ["pauperised"], "6.0 2.3 3.3": ["nanosatellites"], "-3.9 -1.5 7.0": ["superlicence"], "12.2 8.2 11.0": ["pascal"], "7.6 11.7 1.8": ["groundfloor"], "3.2 8.0 -7.8": ["complaing"], "6.1 -10.1 11.3": ["banc"], "13.5 1.2 20.3": ["pinnies"], "-1.9 6.9 14.5": ["intramedullary"], "3.2 18.6 4.9": ["nonobjective"], "-4.9 3.2 0.3": ["deaconesses"], "4.9 18.9 18.2": ["cagier"], "1.9 10.1 6.2": ["briliant"], "-8.9 2.3 5.5": ["tertiles"], "5.0 0.4 20.0": ["lenten"], "3.5 -1.8 12.0": ["bicarb"], "12.2 7.7 21.6": ["nonedible"], "-1.1 2.9 4.4": ["diol"], "15.7 14.2 8.7": ["ashcan"], "-1.1 -0.0 3.2": ["premedicine"], "4.5 14.8 13.0": ["ballmerisanape"], "14.0 0.9 2.7": ["signwriter"], "5.5 11.6 1.1": ["apostolates"], "5.1 10.9 6.2": ["decluttered"], "15.3 19.2 2.4": ["crucifies"], "4.0 0.2 22.8": ["shaun"], "4.8 5.5 11.8": ["kuno"], "15.1 11.7 7.1": ["microlens"], "4.2 11.5 3.6": ["quadrillionth"], "17.2 0.3 3.6": ["technologie"], "13.7 -1.7 24.7": ["jiao"], "9.4 19.3 16.0": ["babbler"], "11.9 10.5 28.9": ["bonsais"], "8.0 17.4 15.7": ["rashad"], "4.4 6.2 8.9": ["championshp"], "8.8 17.4 21.6": ["mesquites"], "7.5 17.6 0.8": ["uncrossable"], "7.1 6.5 12.0": ["motormouthed"], "-3.6 18.2 4.2": ["overclassification"], "-1.3 5.0 2.5": ["contibuted"], "0.6 0.7 -0.5": ["celum"], "17.8 4.0 21.3": ["snowcones"], "11.0 17.0 13.8": ["whammies"], "5.0 14.2 16.2": ["ocha"], "-6.6 13.6 8.4": ["bagh"], "12.5 0.0 8.2": ["versie"], "7.8 4.7 22.3": ["dik"], "1.3 20.1 16.9": ["lurchers"], "5.5 5.8 7.3": ["walkoffs"], "3.4 19.3 3.8": ["refutable"], "-2.4 -3.4 6.1": ["adalats"], "3.7 9.6 -0.8": ["disatisfaction"], "1.5 15.7 10.1": ["gimmee"], "24.5 8.5 26.0": ["splodge"], "1.9 6.4 14.5": ["contrabassoon"], "1.1 8.7 8.7": ["photocalls"], "0.8 -5.3 3.2": ["maintance"], "17.8 0.5 33.2": ["fetta"], "15.8 10.7 34.1": ["fattiest"], "8.3 7.9 11.6": ["antiglare"], "0.6 4.3 -4.3": ["reportes"], "13.0 3.5 13.5": ["photolithographic"], "8.2 2.7 11.1": ["pousada"], "15.1 4.2 9.5": ["nthe"], "19.6 6.4 38.9": ["rissoles"], "3.7 -1.6 15.7": ["tourmalines"], "10.3 5.0 28.2": ["winey"], "10.8 14.6 -4.0": ["securer"], "2.8 3.1 0.5": ["ena"], "3.5 6.7 10.6": ["grat"], "12.9 31.8 9.9": ["sheild"], "2.8 8.0 10.8": ["transwoman"], "-7.5 13.9 12.5": ["kaayo"], "4.3 0.7 10.2": ["cultura"], "3.8 -0.3 8.5": ["epost"], "17.7 0.5 29.1": ["fishways"], "6.1 13.1 11.0": ["klicks"], "7.2 13.5 11.2": ["effulgent"], "-0.3 11.4 12.9": ["multiplications"], "10.9 15.9 10.8": ["sleazeballs"], "20.4 14.1 12.3": ["hackintosh"], "0.2 4.6 0.3": ["childproofed"], "-1.5 15.2 6.1": ["inhere"], "-1.6 -3.3 3.1": ["telecommuted"], "9.4 14.0 22.8": ["linga"], "3.3 5.5 14.8": ["openweight"], "1.6 9.0 -11.1": ["guarantying"], "12.4 3.9 30.3": ["vang"], "-3.5 7.7 10.9": ["nsec"], "-12.0 17.1 2.5": ["dichotomized"], "8.8 13.1 9.2": ["flunkie"], "13.6 1.1 18.9": ["brea"], "17.4 23.5 21.6": ["burliest"], "9.5 0.9 3.2": ["oer"], "10.3 20.7 13.7": ["ooooo"], "-1.3 8.6 2.0": ["authorative"], "1.1 11.8 11.1": ["rematched"], "7.7 0.1 25.9": ["romano"], "3.3 18.1 15.0": ["snickometer"], "4.2 7.0 16.2": ["danceability"], "20.0 -0.9 16.6": ["citigroup"], "9.2 1.1 -3.6": ["mcgeneral"], "12.7 8.5 37.9": ["pistou"], "-3.7 22.5 5.3": ["distinctives"], "4.2 6.3 6.3": ["sollte"], "14.6 6.7 11.0": ["retablo"], "5.2 7.5 14.8": ["cornbelt"], "11.4 21.8 14.8": ["fain"], "2.1 6.2 3.9": ["approriate"], "0.0 5.0 19.2": ["gio"], "1.1 3.6 6.5": ["cetirizine"], "10.7 3.8 15.9": ["subconcession"], "9.1 6.5 17.9": ["tenters"], "4.7 4.7 9.4": ["lipin"], "2.7 14.6 -0.6": ["underinformed"], "2.2 10.8 -0.1": ["eulogises"], "2.3 10.0 18.6": ["nutten"], "7.0 18.3 15.5": ["crabbiness"], "-12.1 3.6 8.5": ["nonattendance"], "-1.1 4.9 15.4": ["gagawin"], "3.5 8.9 9.3": ["boise"], "-3.1 12.4 14.0": ["offspinners"], "0.1 3.2 17.0": ["piperine"], "7.2 0.8 27.4": ["shelly"], "6.4 7.1 15.7": ["transthyretin"], "3.6 7.9 10.6": ["andar"], "-0.6 21.0 2.9": ["voilence"], "8.1 1.7 21.2": ["windsor"], "0.5 4.9 10.7": ["kino"], "-4.6 1.2 13.6": ["kegler"], "2.9 26.5 18.6": ["medevacs"], "4.4 24.4 5.4": ["papist"], "-1.5 -3.9 7.9": ["radiochemical"], "-1.1 10.9 6.4": ["discloser"], "14.9 20.7 10.3": ["mafiosos"], "9.3 14.0 4.4": ["redirector"], "-9.5 5.3 3.1": ["availably"], "2.3 13.0 -0.4": ["multifunctionality"], "4.6 10.5 2.2": ["reacclimate"], "9.5 27.0 14.6": ["brigandish"], "30.6 13.2 12.6": ["trustbusters"], "8.5 16.2 18.5": ["echolocating"], "11.6 15.5 24.0": ["beautyberry"], "5.9 10.2 12.2": ["hypersexualized"], "13.7 21.1 7.2": ["swinish"], "3.4 5.9 4.1": ["wolframite"], "3.7 9.6 5.6": ["serait"], "-1.2 23.4 0.2": ["unarmoured"], "-5.7 6.6 5.2": ["quanity"], "2.1 8.9 10.1": ["garam"], "3.4 11.1 9.2": ["irc"], "5.2 4.0 12.1": ["carotenes"], "-7.8 3.3 7.5": ["homozygotes"], "16.8 9.6 18.6": ["flamin"], "3.2 6.4 37.1": ["bisques"], "-5.7 7.0 9.7": ["nondrinking"], "1.1 11.1 11.1": ["polyarthritis"], "12.3 8.6 3.0": ["carjacks"], "7.0 11.7 17.6": ["casuarina"], "5.0 -6.6 1.4": ["asecond"], "-13.9 -3.5 9.3": ["intersessions"], "-0.5 23.5 11.8": ["underreact"], "11.8 19.2 19.9": ["desiccating"], "-2.5 22.9 3.2": ["desideratum"], "11.9 6.8 7.1": ["chasses"], "9.5 12.8 1.5": ["convenant"], "-2.6 1.7 1.8": ["transmittals"], "8.6 9.9 6.8": ["sudsing"], "7.0 26.3 -0.2": ["sedulously"], "4.6 -3.6 3.3": ["bm"], "6.3 14.1 9.9": ["subwavelength"], "19.9 12.6 6.3": ["recrafting"], "1.1 8.1 8.1": ["preadolescents"], "2.6 10.6 7.3": ["ratiometric"], "0.7 12.7 0.9": ["victimises"], "7.1 0.9 10.0": ["stompbox"], "2.8 4.4 5.2": ["chelator"], "5.4 6.7 14.5": ["mujeres"], "8.1 16.3 6.6": ["movment"], "18.6 6.6 13.9": ["stowable"], "22.0 26.5 16.5": ["electrocutes"], "1.9 0.5 5.4": ["tives"], "3.9 1.5 5.5": ["scarless"], "14.4 14.1 5.4": ["decampment"], "17.7 13.6 23.0": ["patootie"], "-7.6 5.3 8.5": ["multiage"], "9.5 6.9 12.2": ["riveters"], "7.3 9.0 15.7": ["rak"], "17.7 -0.5 11.1": ["skyhigh"], "19.4 3.2 10.8": ["hornbeams"], "10.9 9.0 11.9": ["snyder"], "8.5 4.2 10.8": ["ipa"], "8.0 -1.2 11.2": ["oan"], "-6.8 -2.1 1.1": ["crossgrade"], "0.6 13.4 3.0": ["commu"], "-2.7 10.4 10.0": ["sloka"], "10.2 -3.4 18.9": ["cowhides"], "4.2 1.5 28.1": ["tapenades"], "11.4 5.1 4.7": ["arethe"], "1.1 18.0 5.4": ["yid"], "17.1 21.2 18.5": ["ghosties"], "0.2 9.2 13.4": ["kees"], "3.3 5.7 3.4": ["nonambulatory"], "14.5 19.9 12.3": ["rapelling"], "1.4 1.3 5.7": ["ifrogz"], "2.1 9.9 6.9": ["potentiation"], "-5.0 -6.0 7.0": ["urogynecology"], "8.2 0.4 10.1": ["namings"], "9.9 6.5 11.3": ["twelves"], "15.8 5.4 30.0": ["carmelized"], "7.9 10.5 4.2": ["malaises"], "14.9 -3.5 15.3": ["fresno"], "7.1 8.3 7.6": ["thumbscrew"], "-4.6 8.7 -1.6": ["hydronephrosis"], "-0.9 16.8 3.3": ["politial"], "0.4 6.2 15.9": ["remisier"], "3.5 13.7 13.0": ["adhesiveness"], "9.7 5.6 19.5": ["porto"], "3.6 7.6 8.7": ["meropenem"], "5.9 5.3 -1.2": ["vicotry"], "0.7 1.8 9.3": ["benzoate"], "-0.3 6.2 1.0": ["headmistresses"], "11.3 12.1 9.5": ["barnstorms"], "-2.9 9.2 10.9": ["harambees"], "11.6 9.4 8.0": ["carbonic"], "7.6 5.5 15.5": ["woodfuel"], "11.7 7.9 27.0": ["vireo"], "5.6 4.3 7.5": ["cyclohexane"], "19.2 5.2 18.0": ["edelweiss"], "12.6 5.4 31.3": ["wholewheat"], "9.6 3.7 10.0": ["djuice"], "4.9 15.1 40.9": ["prespawn"], "-1.0 2.4 -0.2": ["recoupable"], "11.0 19.5 39.1": ["grassbeds"], "-2.7 7.0 -4.3": ["pensioning"], "2.6 10.8 7.5": ["blockout"], "17.5 13.0 5.2": ["surrealistically"], "5.0 3.5 10.1": ["colonoscopes"], "0.0 7.2 8.3": ["benzo"], "1.2 9.5 0.9": ["rilpivirine"], "11.1 -0.2 29.7": ["tortelloni"], "-0.5 13.7 -0.1": ["thermotherapy"], "-9.1 7.5 3.5": ["hyperalgesia"], "0.3 -1.2 -3.7": ["thebigword"], "-7.0 13.0 -2.8": ["maulanas"], "10.5 25.8 11.0": ["glitching"], "1.1 0.9 11.4": ["cuvette"], "11.6 1.4 3.7": ["tabloidy"], "5.3 22.7 20.3": ["pinworms"], "13.6 15.7 6.8": ["hybridised"], "8.0 17.3 32.2": ["bract"], "5.4 3.4 8.7": ["cono"], "3.2 13.3 10.0": ["prodigals"], "2.8 10.0 11.5": ["zamindari"], "4.9 5.2 2.8": ["allstars"], "8.4 14.7 13.5": ["sporulation"], "5.2 7.3 -4.2": ["unadvised"], "-1.2 10.3 6.1": ["predistrict"], "-4.3 17.1 -0.8": ["railfans"], "23.8 27.2 8.6": ["indestructable"], "5.2 1.6 7.0": ["scala"], "0.8 -1.0 5.5": ["disodium"], "-5.3 18.8 18.1": ["watchstanders"], "-3.4 7.8 -2.4": ["antithrombotics"], "5.2 13.5 10.0": ["reionization"], "18.7 3.6 1.1": ["hourse"], "5.5 5.1 -3.1": ["nouvelles"], "-1.7 -0.8 5.9": ["cathine"], "18.0 13.0 14.4": ["bleepy"], "15.9 4.3 13.8": ["burgeons"], "14.8 13.8 37.5": ["giblet"], "7.5 21.5 21.8": ["sabot"], "13.5 6.9 7.4": ["diciest"], "1.2 3.3 3.6": ["televoters"], "4.2 14.2 9.6": ["mzungu"], "12.6 9.5 10.7": ["witter"], "3.4 7.8 21.7": ["jian"], "1.3 13.3 6.6": ["morchas"], "1.5 12.1 9.1": ["oversteered"], "-3.5 10.2 0.3": ["furhter"], "1.0 4.6 12.9": ["nadirs"], "12.1 0.2 23.8": ["tweezed"], "17.0 4.6 44.8": ["maguro"], "0.5 3.1 14.0": ["microdiamond"], "6.4 -2.0 -0.4": ["grou"], "7.6 13.0 13.7": ["crosskick"], "12.5 0.0 8.5": ["ramrodding"], "6.7 4.5 1.4": ["futureproof"], "-3.0 -5.0 -1.5": ["urodynamic"], "7.4 1.5 -0.3": ["tolar"], "23.1 2.3 14.6": ["yodelers"], "13.1 12.3 15.8": ["anesthetizes"], "-0.3 6.0 6.7": ["chromites"], "-3.3 17.3 6.0": ["scouters"], "6.6 0.5 3.4": ["chockful"], "1.4 7.4 7.7": ["placarded"], "2.6 13.2 5.8": ["xxviii"], "7.3 6.0 13.0": ["courtney"], "0.4 7.1 4.2": ["transferase"], "-5.1 12.0 9.2": ["chilren"], "9.8 15.4 40.7": ["hawg"], "-1.8 7.3 0.9": ["actigraphy"], "1.4 6.4 8.9": ["colloquies"], "9.1 10.1 10.7": ["septillion"], "3.8 4.6 5.2": ["calcaneal"], "0.4 14.7 10.9": ["chas"], "-4.1 8.4 7.2": ["pancytopenia"], "14.1 10.1 11.6": ["pentacene"], "4.3 26.8 8.3": ["blackshirts"], "7.1 18.9 22.4": ["resprout"], "8.2 15.6 7.0": ["uncomparable"], "4.2 8.2 11.1": ["gail"], "-4.4 11.2 -1.8": ["stae"], "6.2 4.5 13.6": ["eeee"], "8.4 1.1 11.7": ["replacer"], "20.3 5.0 7.6": ["nonpayments"], "2.3 2.2 11.7": ["piperazine"], "13.3 1.5 24.8": ["devon"], "5.2 -3.4 5.6": ["willalso"], "9.7 10.1 16.5": ["felix"], "6.7 12.5 7.0": ["lightbar"], "14.1 34.5 28.4": ["turtling"], "5.7 13.5 17.2": ["netbound"], "26.4 29.0 13.5": ["pugnaciously"], "4.0 4.0 20.1": ["oras"], "-4.6 2.7 10.5": ["burgesses"], "5.3 30.7 10.5": ["reforge"], "-2.9 9.0 5.2": ["oboists"], "3.6 2.1 6.9": ["abegging"], "5.7 13.1 16.2": ["beggarly"], "-6.3 3.5 14.3": ["chak"], "9.1 2.4 4.5": ["nanoscientists"], "-7.1 9.2 -2.2": ["memebrs"], "11.2 16.0 15.0": ["linksland"], "9.3 6.2 2.1": ["risqu"], "9.6 0.5 39.0": ["mignon"], "6.5 8.0 -5.4": ["siginificant"], "4.0 18.1 22.7": ["rototilling"], "-1.0 -2.7 5.1": ["subpostmaster"], "1.7 30.0 9.8": ["israelis"], "-0.4 4.8 3.5": ["dysphonia"], "9.3 24.4 22.7": ["brigs"], "7.8 9.2 6.5": ["wimbledon"], "-10.2 1.9 9.0": ["achalasia"], "5.6 19.6 10.6": ["establishmentarian"], "-0.4 5.2 1.4": ["ultrarunner"], "0.3 5.6 10.4": ["dehiscence"], "4.4 1.6 11.2": ["methacrylate"], "8.9 1.1 13.2": ["daughtercard"], "-3.0 9.8 9.2": ["stylisation"], "12.0 17.8 9.2": ["slobbers"], "18.6 10.5 16.2": ["suckin"], "7.1 2.7 16.8": ["tiangge"], "-0.1 10.5 0.1": ["flagellated"], "5.0 6.7 6.4": ["cabo"], "9.6 26.9 7.3": ["villan"], "-0.7 2.0 10.6": ["ferroportin"], "-4.7 9.4 12.7": ["adat"], "13.7 -1.4 10.4": ["starriest"], "7.8 15.7 10.5": ["ecause"], "-1.5 4.6 2.1": ["doxazosin"], "3.8 14.9 11.3": ["sunderland"], "1.5 9.4 12.7": ["floodline"], "13.9 1.3 33.1": ["cracklin"], "2.8 4.1 4.0": ["duplexers"], "-1.2 38.0 -2.3": ["intell"], "2.6 10.4 9.1": ["conditionals"], "24.1 8.2 14.6": ["titchy"], "-6.6 9.9 4.1": ["ustad"], "9.9 6.6 32.8": ["boxty"], "6.1 24.9 5.3": ["presentiment"], "7.7 4.1 15.9": ["takeway", "twangers"], "9.9 10.7 2.8": ["poland"], "15.2 11.9 22.5": ["fishwife"], "12.6 11.9 26.1": ["jamun"], "4.2 26.4 14.3": ["padawan"], "7.0 10.1 10.8": ["worring"], "6.9 0.7 6.6": ["singlewide"], "2.3 7.0 1.3": ["sexualizes"], "4.9 2.1 3.2": ["desloratadine"], "-2.3 9.9 6.2": ["ically"], "1.1 0.2 2.9": ["initialised"], "1.3 5.0 19.2": ["yata"], "17.8 12.5 33.9": ["avocet"], "2.0 -0.0 7.9": ["ctor"], "10.4 5.9 20.3": ["abuela"], "-1.1 2.8 11.2": ["ances"], "6.1 12.7 48.1": ["bluebacks"], "-4.6 -3.6 3.5": ["outcall"], "-6.7 15.4 0.6": ["sitution"], "4.7 26.9 19.3": ["harborage"], "4.4 5.2 13.3": ["quis"], "8.1 20.0 7.6": ["quicked"], "6.8 13.0 14.7": ["translocating"], "1.8 3.8 7.6": ["kallikrein"], "6.3 -3.4 6.7": ["halalas"], "6.1 4.2 6.2": ["preannounce"], "1.7 4.0 15.4": ["sures"], "-0.7 -4.8 8.7": ["piso"], "4.6 17.7 4.0": ["misdescribed"], "3.0 30.2 5.9": ["polytheist"], "0.8 15.4 13.4": ["feebleminded"], "11.4 7.7 12.2": ["stevie"], "10.1 22.6 1.8": ["furthermost"], "18.8 -0.8 0.4": ["theglobal"], "4.0 8.6 9.6": ["becks"], "-6.1 8.5 11.6": ["numeration"], "6.8 12.9 12.1": ["snowicane"], "4.5 23.1 7.5": ["gunsmoke"], "22.0 7.0 9.8": ["thrummed"], "-3.0 6.9 10.1": ["antioxidative"], "12.1 5.5 4.4": ["hennemusic"], "-4.4 16.4 9.1": ["talentwise"], "10.8 23.1 11.9": ["radioactively"], "-7.6 17.2 10.5": ["khel"], "11.4 15.7 1.2": ["uncloak"], "9.0 -0.7 7.6": ["micrographs"], "13.5 12.6 25.3": ["rheas"], "6.4 -0.4 6.7": ["enzymology"], "10.1 9.2 6.4": ["nanocarriers"], "-8.1 2.7 15.4": ["homebreds"], "4.4 14.7 7.3": ["fannish"], "12.0 0.1 9.5": ["conti"], "13.0 8.7 7.8": ["tightroped"], "-4.0 9.0 7.3": ["hirable"], "7.4 4.4 0.1": ["nanoengineered"], "0.8 7.5 3.5": ["iloprost"], "3.4 27.9 8.5": ["shahids"], "10.7 18.0 28.9": ["merlins"], "9.1 15.1 16.6": ["minger"], "6.1 1.5 9.7": ["rainshower"], "15.8 0.1 3.2": ["steriliser"], "-2.5 9.2 12.2": ["stuffier"], "3.1 9.8 11.3": ["fosamax"], "6.3 7.5 6.7": ["spamfilter"], "-1.5 7.9 -1.3": ["succesor"], "6.0 5.3 13.4": ["fratty"], "-12.1 6.5 -1.0": ["presbyter"], "10.6 16.9 22.0": ["dripper"], "16.2 9.0 31.2": ["tartufo"], "10.9 15.7 7.6": ["skyjacking"], "13.5 8.6 18.5": ["towelette"], "7.1 26.2 29.6": ["decoying"], "-1.8 6.6 28.0": ["qoliqoli"], "7.5 13.8 5.0": ["ntfs"], "-6.7 0.1 6.7": ["fieldworker"], "13.2 1.8 37.5": ["croquetas"], "4.9 10.8 7.8": ["ascensions"], "4.7 5.4 14.9": ["stillage"], "15.2 19.8 13.8": ["schnook"], "6.0 5.7 12.3": ["bluegrassy"], "23.3 11.5 15.8": ["gimcrack"], "6.7 -2.6 8.6": ["locksmithing"], "6.7 9.6 8.9": ["ssl"], "14.2 7.3 8.7": ["posessing"], "4.1 6.0 0.3": ["worthwile"], "25.4 9.6 15.6": ["dayglo"], "-1.0 8.7 3.0": ["hosue"], "8.6 3.6 27.3": ["lomo"], "-10.0 13.7 -0.1": ["overtreat"], "11.4 18.4 33.5": ["driftnet"], "-0.7 5.6 14.8": ["preprocessor"], "6.8 8.1 16.8": ["yama"], "5.6 7.5 6.2": ["sendups"], "16.1 2.0 17.8": ["topknots"], "14.5 8.9 10.2": ["laster"], "10.1 3.2 2.8": ["hardstanding"], "8.0 7.8 1.6": ["demostration"], "-4.0 7.7 8.5": ["anand"], "13.4 2.3 28.2": ["agouti"], "2.6 5.6 4.4": ["tg"], "2.2 4.1 12.3": ["phensidyl"], "6.1 12.3 -3.7": ["ministeries"], "13.0 10.4 17.8": ["castellated"], "0.3 -0.3 9.1": ["monologuist"], "18.4 17.6 12.8": ["timewasters"], "17.0 5.8 19.3": ["crusties"], "14.2 23.1 13.8": ["shoguns"], "-1.1 9.3 9.6": ["majalis"], "5.6 13.5 11.1": ["disquietingly"], "11.7 7.1 12.3": ["seigneur"], "1.6 4.7 7.6": ["steets"], "6.8 14.8 11.0": ["meson"], "12.5 17.3 9.0": ["forebodes"], "2.8 15.3 2.7": ["bankmen"], "10.2 10.2 3.7": ["attuning"], "5.8 8.2 12.4": ["abhishek"], "6.3 9.2 18.9": ["nonfarmers"], "3.1 9.6 1.2": ["aircard"], "17.9 0.6 10.8": ["pressboard"], "20.5 34.9 19.6": ["lycanthropes"], "1.3 5.6 -1.3": ["getreading"], "11.8 7.5 13.3": ["sizers"], "17.1 1.9 19.0": ["musette"], "8.3 3.1 29.4": ["funghi"], "11.8 11.0 21.9": ["resaca"], "2.3 10.1 16.5": ["hardeners"], "2.3 10.9 11.5": ["breeziest"], "9.9 5.1 26.2": ["laddoo"], "18.9 24.2 16.9": ["mercantilists"], "7.3 1.8 12.8": ["synopsized"], "3.7 0.8 14.1": ["freckling"], "-2.5 14.3 0.3": ["bunglow"], "11.5 6.8 13.0": ["corridas"], "5.3 1.8 7.6": ["canonizations"], "-0.5 -0.6 4.9": ["compte"], "-2.9 10.3 -2.1": ["ministrys"], "1.9 -0.7 17.1": ["firelogs"], "12.2 12.7 18.5": ["seahawks"], "11.5 -0.2 10.2": ["carbonization"], "2.3 -2.8 0.9": ["putable"], "14.1 2.2 10.2": ["nanofluidic"], "8.3 1.3 6.9": ["rapidshare"], "3.5 14.2 5.4": ["adhan"], "3.1 -8.9 9.8": ["innaugural"], "16.4 6.1 7.2": ["megastardom"], "-4.3 -2.9 9.0": ["secnd"], "7.8 13.2 11.4": ["frontrowers"], "32.5 10.9 -3.6": ["megabrands"], "5.7 12.4 10.1": ["orienteer"], "14.2 10.4 14.0": ["danzon"], "6.6 11.7 6.0": ["debonaire"], "20.8 12.3 6.3": ["campest"], "0.7 11.7 17.9": ["chlorosis"], "2.3 15.8 6.6": ["measureables"], "14.1 10.8 17.4": ["chronometers"], "-3.5 14.0 18.1": ["dewormers"], "2.1 6.9 10.0": ["ultrarunning"], "6.4 8.3 9.2": ["radiopaque"], "8.4 20.1 17.7": ["fumigators"], "14.1 15.4 26.6": ["tenderizer"], "8.9 13.4 8.9": ["featurephones"], "0.1 -1.2 3.7": ["fundoplication"], "5.8 2.8 5.7": ["mkv"], "16.8 18.6 31.6": ["greenfly"], "-5.7 1.9 7.5": ["ovulatory"], "-2.6 8.4 -3.5": ["uncertificated"], "5.5 5.1 8.0": ["retiling"], "9.2 10.8 11.7": ["opec"], "-0.4 12.9 8.1": ["sporter"], "8.8 3.2 12.6": ["sprue"], "8.0 14.1 7.9": ["narcoleptics"], "3.1 16.9 0.6": ["tailorable"], "7.9 20.2 4.1": ["blasphemes"], "12.5 17.5 5.2": ["feudalist"], "-0.2 -4.4 4.4": ["unversity"], "-0.9 0.2 13.5": ["transbay"], "-6.5 9.6 5.6": ["scence"], "4.4 3.2 3.5": ["neuf"], "-0.0 15.1 6.5": ["ambulancemen"], "1.5 1.0 12.9": ["supermodifieds"], "24.3 21.1 22.6": ["doglike"], "4.7 15.1 14.7": ["nonradioactive"], "1.1 -0.1 11.2": ["destock"], "2.7 2.6 5.7": ["twinjets"], "8.3 14.0 15.0": ["hussle"], "1.8 0.7 15.0": ["hydrous"], "6.1 2.7 22.3": ["offals"], "8.9 13.1 15.2": ["nanoshell"], "10.5 -1.3 28.0": ["hoa"], "-15.5 -2.2 11.4": ["eligibilities"], "-10.0 2.1 2.7": ["negotiability"], "-1.1 16.6 27.5": ["nonhunters"], "8.2 7.5 12.8": ["bepotastine"], "3.5 2.0 15.8": ["huntington"], "0.1 5.5 -4.3": ["proffessional"], "19.5 7.9 17.8": ["bailers"], "11.3 5.8 12.0": ["memcpy"], "22.5 12.8 16.7": ["flinger"], "1.5 6.2 5.7": ["taked"], "17.4 7.0 13.9": ["swills"], "5.9 12.0 12.5": ["rho"], "-11.2 0.8 9.1": ["exceedences"], "4.0 10.7 10.8": ["epicentred"], "23.6 16.3 9.5": ["adver"], "-1.3 -0.8 9.8": ["stet"], "1.9 8.9 7.3": ["smidgin"], "11.6 12.7 13.5": ["firestarters"], "4.8 0.2 3.4": ["nitrides"], "-10.5 11.8 6.4": ["halachically"], "-0.4 13.4 0.5": ["fullfilling"], "23.9 8.9 4.8": ["ceos"], "8.8 14.7 -1.6": ["faithfull"], "-3.1 2.4 7.6": ["micromoles"], "8.5 12.2 17.5": ["bedliners"], "10.2 16.4 16.0": ["crustiest"], "6.1 4.2 4.1": ["afterwork"], "-1.2 0.1 6.9": ["gard"], "7.8 12.1 10.2": ["vette"], "11.0 15.5 8.9": ["rollocking"], "12.6 10.3 10.1": ["boofhead"], "22.8 20.8 14.1": ["unqiue"], "4.6 0.0 12.2": ["replastering"], "19.6 6.3 28.5": ["duckie"], "4.2 7.5 2.3": ["formatter"], "-11.1 11.0 11.7": ["postemergence"], "6.3 5.0 5.6": ["catcalled"], "2.4 10.1 10.1": ["anthologist"], "17.1 7.7 7.5": ["correlator"], "-0.9 11.7 27.7": ["metaldehyde"], "-3.2 6.4 9.8": ["lordosis"], "1.7 13.7 7.3": ["brickwall"], "22.9 13.2 7.9": ["churner"], "6.9 9.5 -0.9": ["proselytizes"], "-4.8 5.4 7.8": ["leigh"], "6.2 11.9 11.3": ["jimmying"], "5.2 6.0 23.1": ["aquaponic"], "1.8 12.2 -3.0": ["provacative"], "11.4 9.9 30.8": ["ichthyology"], "6.5 13.5 3.0": ["agenting"], "-7.4 4.2 6.9": ["cholestasis"], "-2.3 10.4 1.7": ["autodialer"], "8.1 16.4 12.5": ["stonily"], "3.6 0.1 3.7": ["undercharges"], "17.5 8.0 7.5": ["floggers"], "16.6 -3.5 3.9": ["grubstake"], "11.4 6.2 14.4": ["goldendoodle"], "-5.3 2.4 8.8": ["neices"], "3.1 10.3 5.0": ["washerman"], "13.8 -3.0 7.5": ["unprecidented"], "3.5 1.8 12.8": ["promgoers"], "8.8 20.4 8.8": ["politricks"], "12.2 13.2 10.0": ["dogfooding"], "10.4 23.9 14.7": ["veracious"], "3.8 14.0 6.6": ["unsubscribes"], "6.4 8.6 4.3": ["deice"], "7.2 11.1 5.7": ["pursuiters"], "10.5 6.8 22.6": ["peplums"], "-1.4 10.1 3.8": ["waas"], "8.2 -0.8 9.2": ["viols"], "-2.4 6.7 11.8": ["masyado"], "7.0 6.1 13.4": ["kudofest"], "10.7 9.5 6.5": ["freesat"], "18.0 14.3 19.7": ["tricolored"], "1.7 10.0 17.0": ["calculi"], "8.5 8.7 11.0": ["clubbiness"], "-3.7 3.2 -0.4": ["nonroutine"], "14.8 11.7 11.8": ["shlub"], "9.8 7.1 10.3": ["bashment"], "1.6 -0.7 18.4": ["burke"], "13.3 15.7 -2.6": ["gassings"], "8.2 5.0 6.5": ["icyou"], "2.4 15.6 4.1": ["armodafinil"], "5.6 8.3 13.0": ["partyin"], "3.7 9.3 12.0": ["rakia"], "-1.6 2.6 7.0": ["unemployability"], "11.0 13.6 1.8": ["ressources"], "10.6 16.6 10.5": ["sultanates"], "8.3 18.3 6.6": ["moneyball"], "7.5 7.1 15.5": ["visarjan"], "7.2 16.8 10.7": ["denouements"], "1.0 1.0 3.4": ["freecall"], "-1.5 -2.9 15.0": ["marijauna"], "-3.8 3.3 7.2": ["timolol"], "27.4 -6.6 -5.1": ["lauches"], "14.7 10.2 16.0": ["spheroids"], "13.4 4.1 11.0": ["reat"], "-1.6 20.7 0.2": ["opion"], "6.3 0.7 9.1": ["geotech"], "3.7 5.1 17.5": ["jejunum"], "11.2 12.1 8.2": ["chivalrously"], "-0.3 3.5 8.2": ["laproscopic"], "-1.8 11.6 2.0": ["votegetters"], "0.4 12.4 9.4": ["dissaving"], "6.4 5.8 5.8": ["damange"], "-0.7 3.1 16.9": ["gung"], "16.0 5.6 8.4": ["barrista"], "2.0 5.6 -4.3": ["presiden"], "7.0 4.3 16.9": ["menuing"], "-1.1 7.7 6.7": ["benazepril"], "8.3 14.2 6.8": ["nonexplosive"], "-3.0 -2.7 -1.9": ["physiatrists"], "2.0 8.1 4.9": ["thesauri"], "22.3 13.0 17.1": ["stormers"], "3.7 4.3 19.1": ["evenin"], "3.8 2.3 -1.3": ["silanes"], "11.3 2.3 23.8": ["handblown"], "6.3 0.5 9.5": ["designo"], "2.9 8.7 7.8": ["arbitrages"], "5.5 9.4 12.7": ["screenwash"], "8.1 26.8 13.1": ["henchwoman"], "19.0 -3.7 1.6": ["freezone"], "6.9 11.7 13.6": ["mazaar"], "12.2 -5.4 7.9": ["quarte"], "11.1 5.6 13.2": ["pashing"], "9.0 20.0 11.3": ["superkicked"], "3.5 0.4 27.1": ["primi"], "6.3 5.3 12.7": ["lifechanging"], "-1.4 10.1 15.3": ["oligomeric"], "6.0 -0.1 8.7": ["kien"], "-7.7 -3.0 2.3": ["housemanship"], "12.2 1.8 10.7": ["octuplet"], "1.7 7.6 13.3": ["mesenchyme"], "17.2 15.2 9.4": ["dirigisme"], "10.4 14.0 6.2": ["reabsorbing"], "3.4 -0.7 14.3": ["nus"], "4.1 6.5 0.9": ["aera"], "2.4 4.0 13.2": ["coeur"], "2.9 11.6 12.4": ["fulham"], "8.0 4.7 13.6": ["clarke"], "4.5 24.7 8.5": ["stickhandler"], "-2.2 -9.4 4.1": ["softbound"], "6.0 -0.3 11.0": ["sevenyear"], "4.8 18.6 7.8": ["uncynical"], "0.1 8.6 9.0": ["visco"], "18.2 4.1 11.3": ["sousaphones"], "15.0 12.6 12.0": ["strimmers"], "8.0 11.6 10.7": ["frightfest"], "2.6 7.7 1.1": ["consentual"], "8.3 8.5 5.0": ["babymama"], "6.1 10.0 11.0": ["noncoding"], "-1.5 11.2 15.0": ["sahur"], "4.3 14.3 33.4": ["bonefishing"], "8.4 14.6 20.8": ["deckhouse"], "6.7 8.6 12.1": ["ernest"], "6.2 7.0 7.3": ["waren"], "1.9 -2.2 13.7": ["lus"], "6.6 0.0 -1.2": ["asx"], "7.4 9.1 19.1": ["azurite"], "2.3 4.3 7.7": ["unrestrictive"], "-7.6 4.2 4.9": ["firstbaseman"], "9.8 9.8 11.0": ["bifurcates"], "12.0 -3.5 6.0": ["andan"], "3.5 15.4 7.3": ["pnuemonia"], "-0.8 6.6 13.3": ["widish"], "3.5 20.5 4.9": ["downbursts"], "9.3 23.2 19.8": ["desiccate"], "22.1 1.4 16.0": ["lubing"], "16.2 3.8 25.8": ["unwaxed"], "1.4 -9.5 10.5": ["eyar"], "1.9 17.2 12.5": ["glidepath"], "-0.5 3.1 5.0": ["nonrandom"], "6.9 10.7 11.5": ["uncrossing"], "3.1 6.2 8.5": ["backhauled"], "-0.5 -0.1 9.4": ["chautauqua"], "19.1 21.9 9.1": ["forebodingly"], "5.5 21.3 10.2": ["immutably"], "-8.3 -4.0 3.6": ["postnatally"], "-0.2 12.3 7.6": ["traceless"], "-1.3 16.6 9.9": ["rangatiratanga"], "8.3 9.5 7.3": ["recruitniks"], "12.4 18.8 6.4": ["divisons"], "8.6 15.2 16.7": ["bellringer"], "7.9 7.7 22.1": ["tubig"], "1.2 -2.5 1.8": ["reciepts"], "10.8 5.6 -0.9": ["cyberculture"], "17.8 -0.5 23.9": ["lavendar"], "-4.1 33.8 1.9": ["salafi"], "-6.2 1.0 8.2": ["mmcfpd"], "-1.4 -1.1 26.2": ["anejo"], "-4.7 9.2 7.8": ["nonparametric"], "17.7 5.1 17.5": ["rollerskate"], "12.8 6.0 3.9": ["flybe"], "7.5 -2.2 12.8": ["edmonton"], "9.7 10.2 7.9": ["turbulance"], "21.5 9.9 16.9": ["spectactular"], "4.8 13.7 7.2": ["botheration"], "7.2 8.2 3.6": ["integrals"], "4.8 17.1 8.7": ["crips"], "7.6 -3.9 9.5": ["maestra"], "3.8 14.2 21.6": ["scratchin"], "-10.5 10.3 -2.6": ["relatedly"], "11.3 -4.3 22.5": ["lunchmeats"], "2.3 10.0 14.1": ["manumatic"], "8.2 13.4 5.4": ["reignition"], "22.9 4.5 11.1": ["geegaws"], "5.0 2.0 9.6": ["ellis"], "3.2 -1.8 14.0": ["septa"], "10.4 16.7 1.6": ["repudiations"], "10.9 -0.0 11.4": ["labeller"], "-9.0 18.2 7.3": ["actionability"], "-0.9 17.5 -1.9": ["tirelessness"], "9.8 -0.8 -4.5": ["reprofile"], "14.4 13.6 14.0": ["contortionism"], "2.8 9.5 3.7": ["idiomatically"], "-1.1 18.1 4.2": ["actully"], "2.1 11.8 9.9": ["earldom"], "5.8 3.2 16.4": ["unwrought"], "17.4 11.5 17.5": ["unhooks"], "5.8 16.6 13.8": ["servitors"], "8.0 6.2 18.1": ["bou"], "4.3 12.6 8.8": ["fingerwork"], "6.6 4.3 8.6": ["embosser"], "-5.0 11.4 7.8": ["mocetinostat"], "6.8 2.7 5.5": ["norbolethone"], "15.1 23.1 12.7": ["brushlands"], "17.1 4.9 2.0": ["technopark"], "-0.1 22.5 -5.3": ["threatning"], "-3.4 6.5 2.5": ["dialyze"], "9.4 9.2 32.5": ["zester"], "0.9 33.3 3.9": ["eelam"], "0.3 1.9 12.1": ["davies"], "3.9 19.9 7.0": ["straighforward"], "6.7 2.1 1.2": ["carrera"], "7.5 9.0 12.1": ["johnr"], "0.8 9.7 3.6": ["streeting"], "8.1 12.5 -0.4": ["audiance"], "-4.1 5.1 4.2": ["delafloxacin"], "9.8 14.2 11.0": ["caput"], "14.2 13.5 9.2": ["discusting"], "10.6 4.6 14.9": ["appetitive"], "-7.7 4.8 1.5": ["compartmentalizes"], "4.4 0.8 13.9": ["folksters"], "1.9 9.4 -0.0": ["dissappointment"], "9.6 25.1 5.2": ["helicoptor"], "0.4 -0.2 13.7": ["aberrantly"], "7.8 4.7 14.0": ["quoi"], "9.0 18.4 18.2": ["winkingly"], "16.2 25.7 15.1": ["endlessness"], "-1.8 1.3 -0.7": ["dicussions"], "7.4 9.0 17.3": ["hotbox"], "13.7 12.7 13.6": ["quokka"], "12.8 8.2 36.1": ["tonkatsu"], "6.7 13.7 12.0": ["melanocyte"], "16.5 9.0 29.7": ["whorled"], "6.4 5.9 -3.7": ["realted"], "4.6 3.1 13.8": ["mulesed"], "-1.1 21.2 10.9": ["istan"], "-0.6 7.2 9.8": ["cody"], "8.6 10.3 12.2": ["bansuri"], "-2.4 -0.9 4.3": ["bri"], "7.0 12.5 12.8": ["parenchyma"], "3.2 15.6 4.3": ["redownload"], "2.1 -0.9 7.0": ["conte"], "8.7 -2.0 8.6": ["trodusquemine"], "23.2 21.6 15.9": ["strangelets"], "5.2 13.6 14.4": ["slightness"], "6.2 14.8 9.2": ["suitablef"], "3.3 3.9 5.5": ["acetic"], "-7.0 20.7 6.6": ["tzaddik"], "3.4 12.1 16.7": ["sailmakers"], "-1.7 7.9 20.9": ["pumpout"], "-4.6 9.4 7.5": ["quals"], "0.4 16.6 15.5": ["cuvettes"], "4.1 1.3 13.1": ["dartball"], "3.4 13.6 5.3": ["pradhans"], "2.4 9.9 -2.6": ["achivements"], "14.2 3.5 20.1": ["crockpots"], "22.0 7.4 24.8": ["mandrills"], "2.2 17.5 6.5": ["interfer"], "10.0 34.6 7.7": ["destructibility"], "11.2 10.9 7.2": ["flapdoodle"], "5.1 19.2 11.0": ["aftertouch"], "8.1 16.3 10.1": ["nimbys"], "19.9 16.4 14.7": ["snuffles"], "7.6 16.2 11.0": ["meganucleases"], "5.9 6.3 13.5": ["trabajo"], "4.6 9.3 15.5": ["nakita"], "2.4 11.9 7.7": ["quadraplegic"], "5.6 -0.4 19.1": ["hala"], "-8.2 7.3 4.8": ["abdul"], "-7.7 3.1 -5.7": ["representitive"], "13.9 4.7 6.2": ["functionless"], "2.2 2.9 33.0": ["foodshed"], "-2.0 1.4 0.5": ["olders"], "8.5 4.7 3.2": ["vitalization"], "11.3 8.7 7.5": ["perfomer"], "16.4 7.3 4.0": ["deutsche"], "0.3 1.5 10.1": ["assemblymember"], "3.2 9.8 8.0": ["tweenagers"], "13.7 9.1 3.4": ["redomicile"], "3.0 9.3 12.7": ["radiolucent"], "-1.7 2.5 7.4": ["sbs"], "-8.1 9.2 -0.4": ["xxxxxxxxxxxx"], "0.1 12.4 6.2": ["presssure"], "4.6 9.6 6.1": ["beatsmith"], "17.9 8.6 21.1": ["scepters"], "9.3 9.6 23.3": ["faceup"], "5.8 12.5 5.8": ["schoolmarmish"], "7.2 13.9 10.3": ["humorlessness"], "-0.1 3.2 -3.4": ["receipient"], "1.8 6.9 8.1": ["medially"], "2.0 10.8 13.8": ["sparc"], "5.6 13.1 16.7": ["disked"], "13.1 -6.8 -2.2": ["projets"], "24.5 10.1 18.1": ["bungees"], "3.3 -0.2 13.9": ["mesta"], "0.4 3.7 13.6": ["pennyweight"], "11.9 14.3 4.8": ["eejits"], "0.3 -1.1 8.8": ["preg"], "2.6 3.9 9.9": ["chikankari"], "13.2 12.5 12.4": ["rebus"], "-1.1 9.6 0.3": ["secretaryship"], "6.0 16.7 4.8": ["hackwork"], "8.4 20.2 5.5": ["slamdunk"], "0.1 14.4 4.7": ["symbologies"], "-4.4 15.3 6.9": ["yadav"], "17.5 8.1 9.1": ["subdermal"], "6.8 18.1 9.2": ["decontextualized"], "-1.1 2.8 13.8": ["cruisetour"], "19.2 -8.1 20.5": ["innertubes"], "4.5 4.6 2.8": ["coachbuilt"], "1.1 17.2 23.3": ["wingshooting"], "10.9 7.0 2.1": ["stablising"], "0.4 10.1 12.2": ["leprosarium"], "7.3 3.5 21.6": ["pei"], "-3.2 5.5 14.4": ["dalawa"], "2.6 4.6 17.2": ["boardsailing"], "-3.7 9.7 2.2": ["republishes"], "4.5 12.1 7.7": ["freeflowing"], "16.8 10.6 19.1": ["carney"], "14.7 20.7 17.0": ["wimpier"], "-1.6 26.3 0.6": ["basiji"], "6.2 3.8 10.3": ["netribution", "besar"], "15.9 13.0 17.1": ["geoglyphs"], "-3.0 -0.8 0.3": ["hardcopies"], "-5.5 7.4 22.3": ["hayed"], "14.3 -0.4 20.3": ["feedmill"], "-1.2 7.3 11.3": ["refranchised"], "7.5 19.1 7.0": ["autobiographer"], "3.6 0.5 6.4": ["ayuda"], "18.3 3.8 11.4": ["schmoozefest"], "-0.7 12.7 11.4": ["archeologically"], "-3.1 6.1 4.5": ["namedrop"], "16.0 6.7 -3.4": ["bestknown"], "12.0 8.3 11.8": ["norwegian"], "22.1 13.4 22.1": ["grindstones"], "13.0 10.9 18.9": ["dane"], "5.2 17.7 4.2": ["shortsightedly"], "5.5 10.1 40.9": ["giardiniera"], "4.7 10.2 4.1": ["ophthalmoscope"], "8.2 0.5 2.3": ["aftershaves"], "6.1 10.7 27.5": ["semitropical"], "6.4 3.1 3.1": ["firts"], "-0.0 -2.1 12.9": ["rehersal"], "-4.4 -1.2 6.6": ["performaces"], "5.0 8.7 13.0": ["biculturalism"], "15.8 15.6 10.7": ["unprofitably"], "3.9 5.5 7.6": ["hafltime"], "13.4 11.0 21.6": ["caws"], "-1.4 8.1 8.7": ["outproduced"], "7.0 0.9 6.6": ["patriach"], "8.7 4.3 28.8": ["ume"], "2.5 1.3 -3.0": ["amiando"], "5.2 3.3 9.1": ["yeye"], "4.6 -4.0 12.5": ["northshore"], "11.1 12.5 11.9": ["firewalk"], "9.8 15.7 6.6": ["quasiparticles"], "16.8 26.9 16.1": ["dirtball"], "5.6 18.6 17.9": ["ossify"], "10.3 -0.3 20.3": ["benny"], "11.2 20.1 13.7": ["braggadocios"], "-1.2 11.9 8.3": ["scooterists"], "6.1 10.2 21.2": ["algaecide"], "-10.3 3.9 2.6": ["noncardiac"], "10.4 2.6 9.1": ["ultrawealthy"], "7.7 5.1 8.6": ["erie"], "11.0 17.8 8.1": ["boaster"], "12.1 14.5 12.4": ["catwoman"], "3.4 11.8 -1.0": ["reorientate"], "10.9 2.1 29.1": ["sautee"], "11.6 14.2 37.3": ["redshank"], "19.3 4.0 33.5": ["homefries"], "-6.2 4.4 14.0": ["basinwide"], "15.3 8.3 11.4": ["looooove"], "11.5 13.8 14.7": ["rutty"], "9.6 1.5 0.1": ["microbubble"], "1.4 1.4 11.3": ["plenums"], "13.7 18.0 6.0": ["hoaxing"], "-2.5 23.5 5.1": ["divisively"], "-2.5 4.7 0.2": ["kpbs"], "6.2 1.1 -0.7": ["conceiver"], "7.3 8.9 19.0": ["goiters"], "11.9 11.7 10.4": ["acronymic"], "4.7 5.1 22.6": ["sunbirds"], "-2.7 9.8 -0.2": ["cariprazine"], "2.0 7.3 10.1": ["framebuffer"], "8.0 3.6 25.7": ["snifters"], "11.8 34.3 14.1": ["terrority"], "-4.0 18.0 6.8": ["momentums"], "4.4 11.3 17.2": ["nim"], "4.4 8.1 35.0": ["rajma"], "-6.2 12.9 8.1": ["bedoon"], "7.5 11.0 18.9": ["saponin"], "6.1 -1.8 -3.3": ["outleaned"], "0.5 9.8 4.6": ["custodies"], "-2.5 -2.9 3.6": ["channelisation"], "8.5 10.9 3.4": ["supercoach"], "12.9 25.8 0.5": ["decieve"], "1.3 15.1 2.8": ["plagiarizes"], "20.6 11.1 19.5": ["sculpturally"], "10.1 3.3 0.3": ["acheter"], "2.8 10.0 5.6": ["iroxanadine"], "11.1 2.9 2.6": ["fillable"], "4.4 16.8 2.5": ["chowkies"], "18.9 6.5 41.1": ["kabocha"], "-4.5 6.0 8.3": ["solemnisation"], "21.6 16.4 4.1": ["massless"], "3.8 -4.7 3.6": ["underbilled"], "5.7 18.1 2.2": ["undiplomatically"], "6.5 21.9 11.4": ["deflationist"], "13.8 12.1 4.9": ["chivvy"], "-9.9 8.6 8.0": ["thiazides"], "8.6 2.2 33.2": ["transferware"], "3.0 4.5 7.9": ["multiprocessors"], "3.0 35.7 9.8": ["squadmate"], "10.6 1.3 13.0": ["bryant"], "7.2 17.4 4.7": ["prettifying"], "2.6 6.7 10.0": ["sitdowns"], "-0.7 8.5 6.0": ["listicle"], "15.0 2.0 11.3": ["fibreoptic"], "0.3 2.8 0.8": ["ofer"], "5.8 20.4 9.3": ["ballhog"], "5.7 9.0 12.3": ["revegetating"], "0.0 13.1 29.8": ["tippets"], "9.6 11.7 4.9": ["cyberdissidents"], "15.9 8.9 29.7": ["frogspawn"], "12.1 0.7 34.1": ["benedict"], "9.7 13.8 20.8": ["drowsing"], "6.0 14.8 7.0": ["broadbrush"], "12.5 16.6 25.1": ["sots"], "-3.2 4.0 0.1": ["glutaraldehyde"], "0.4 2.3 10.0": ["planarization"], "7.8 8.9 12.5": ["bia"], "1.9 6.0 13.8": ["kotha"], "14.8 11.0 8.6": ["heatless"], "9.7 15.2 10.8": ["runescape"], "16.1 6.9 0.5": ["djay"], "5.8 2.9 -6.2": ["saidon"], "1.1 0.1 1.3": ["cph"], "-1.0 4.2 -0.7": ["secondplace"], "4.0 2.9 4.5": ["tremelimumab"], "-0.6 13.8 4.7": ["andolan"], "6.6 6.6 10.2": ["streetfront"], "19.1 14.7 22.2": ["rocklike"], "3.6 8.0 4.9": ["eventless"], "9.9 8.2 8.6": ["ibook"], "-4.4 13.6 9.0": ["choroidal"], "4.1 8.0 6.3": ["anaphase"], "11.6 10.2 17.9": ["coulter"], "10.9 9.3 33.7": ["marination"], "-1.1 -3.6 1.7": ["espoir"], "3.3 11.2 15.6": ["backwashing"], "1.1 8.2 11.0": ["undervoltage"], "10.2 15.2 4.0": ["signficance"], "12.8 12.6 9.2": ["trekkies"], "5.3 10.9 3.2": ["necesssary"], "1.7 6.6 7.4": ["tonearm"], "4.3 14.1 6.2": ["victimes"], "1.0 3.4 -0.0": ["coucil"], "7.4 14.1 4.9": ["unmount"], "6.2 7.3 27.8": ["banders"], "-0.9 3.5 14.8": ["vio"], "0.1 10.1 6.5": ["serviceably"], "11.9 23.3 4.4": ["neofascist"], "10.5 20.5 7.1": ["superhumanly"], "5.7 -0.3 22.9": ["francaise"], "-1.3 3.8 10.5": ["geomorphologist"], "8.0 -6.4 18.4": ["shorthorn"], "3.4 -0.6 1.6": ["undersung"], "-1.9 6.2 14.3": ["panahon"], "6.1 7.1 13.3": ["sneakerhead"], "-6.6 9.7 6.8": ["treprostinil"], "-5.9 11.7 8.1": ["noncom"], "2.9 5.3 12.2": ["unmannered"], "7.8 6.3 7.5": ["foundlings", "sidestream"], "-2.2 4.7 8.1": ["paresthesias"], "5.0 17.2 8.1": ["talismen"], "-4.3 15.3 -0.4": ["dilligently"], "3.5 5.0 22.1": ["surfski"], "5.5 15.3 13.8": ["resegregate"], "0.6 7.2 4.9": ["teamtalk"], "10.6 3.9 8.1": ["alco"], "14.6 8.3 14.7": ["replastered"], "6.1 22.7 3.9": ["schismatics"], "13.9 11.3 46.6": ["hardhead"], "2.0 1.5 1.7": ["mismarking"], "-1.4 -1.1 11.0": ["fwiw"], "6.3 21.1 27.7": ["parasitoid"], "4.0 15.4 9.7": ["naturalistically"], "9.3 -0.1 3.8": ["throgh"], "11.4 8.8 12.4": ["aristos"], "11.3 9.0 15.9": ["natura"], "5.1 14.4 6.2": ["wihtout"], "-6.0 -1.4 4.7": ["mwh"], "2.6 13.9 18.7": ["mycorrhizae"], "-0.0 9.4 17.3": ["budgeter"], "1.7 -8.7 1.6": ["dello"], "9.2 11.5 5.4": ["chattiest"], "8.0 11.2 7.8": ["negawatts"], "10.6 15.8 15.0": ["reflooding"], "9.8 23.6 6.7": ["horsewhipped"], "-4.9 12.0 -2.5": ["consituency"], "7.9 -2.8 1.7": ["buliding"], "1.1 4.9 0.7": ["ssed"], "10.2 6.2 41.1": ["coalfish"], "9.2 10.8 2.1": ["pursuaded"], "-4.6 12.1 1.7": ["deducible"], "10.4 -0.0 18.8": ["lupa"], "7.0 -0.4 12.8": ["leslie"], "8.1 14.1 10.0": ["unclassy"], "9.2 -2.6 11.9": ["fleur"], "13.5 8.9 10.6": ["mailorder"], "11.1 8.9 1.6": ["overworks"], "6.4 18.8 6.9": ["solicitousness"], "5.8 -0.2 13.5": ["mieux"], "13.3 -5.1 17.2": ["slingback"], "11.9 10.1 14.7": ["gooood"], "3.1 15.1 15.6": ["hawa"], "3.6 4.0 9.4": ["alunite"], "5.6 27.4 8.9": ["redcoat"], "2.8 1.7 8.6": ["chome"], "-3.6 9.9 7.9": ["passivated"], "1.7 8.0 15.2": ["runless"], "3.2 16.2 8.1": ["hostaged"], "24.5 13.7 19.2": ["wraithlike"], "8.1 -3.6 2.7": ["publi"], "15.9 4.2 12.4": ["bearlike"], "3.7 13.6 7.3": ["forename"], "-0.3 16.4 9.2": ["guerra"], "8.9 2.0 13.1": ["tanga"], "8.3 15.6 4.6": ["strategics"], "6.9 8.4 1.6": ["creater"], "-10.7 12.7 9.1": ["definiteness"], "3.5 11.1 10.4": ["reacquaintance"], "3.4 8.4 9.9": ["neurotrophin"], "-4.7 -4.9 6.9": ["phonathon"], "10.0 4.6 14.4": ["sebaceous"], "22.1 3.3 22.5": ["bubblewrap"], "9.2 14.6 4.7": ["precendent"], "0.2 -4.8 12.5": ["villagewide"], "5.9 10.0 2.1": ["excrutiating"], "8.8 32.3 11.9": ["counterspace"], "12.7 14.0 14.4": ["bru", "whuppings"], "0.4 0.7 10.5": ["topnotchers"], "-2.7 13.0 11.4": ["fide"], "2.8 8.5 10.5": ["enzymatically"], "0.9 9.5 7.3": ["toolholders"], "6.8 18.1 3.4": ["sympatico"], "12.3 27.5 11.2": ["petrifies"], "-6.5 4.3 2.4": ["laicize"], "6.2 2.5 30.4": ["emmer"], "18.4 4.3 15.8": ["tig"], "-5.9 17.0 1.4": ["psychologic"], "10.9 18.8 13.4": ["haunters"], "18.3 7.0 12.1": ["emery"], "0.5 2.7 -2.5": ["orthosis"], "28.5 14.5 6.9": ["phonemaker"], "-0.2 10.1 6.3": ["unanchoring"], "2.3 -2.2 7.5": ["telemarking"], "1.6 6.8 0.4": ["gulity"], "10.6 15.6 13.8": ["arraying"], "5.0 3.4 3.4": ["fusible"], "22.3 12.1 20.1": ["octagons"], "11.5 0.7 8.0": ["preneurs"], "6.1 5.8 13.4": ["beofre"], "7.5 12.1 11.6": ["footsies"], "9.2 13.9 9.5": ["overskated"], "-2.4 -3.0 6.2": ["ela"], "-4.1 11.2 -2.5": ["forfeitable"], "14.8 19.2 12.3": ["scarefest"], "14.9 7.6 6.8": ["hunkiest"], "-3.7 1.3 4.4": ["myeloperoxidase"], "13.3 6.9 10.0": ["nanometric"], "4.1 1.7 11.0": ["desiccants"], "19.7 5.5 28.0": ["butties"], "6.0 11.0 17.2": ["butterbur"], "3.2 9.5 4.5": ["headscratcher"], "26.0 40.4 16.1": ["superweapon"], "8.4 11.2 -0.4": ["mobilities"], "1.6 9.1 15.3": ["nau"], "5.6 13.9 10.4": ["typeof"], "7.1 9.1 6.8": ["whay"], "15.9 7.2 1.5": ["lmost"], "3.8 7.6 4.9": ["seatholder"], "-4.6 7.6 3.5": ["methemoglobin"], "-3.0 10.4 0.3": ["absenting"], "8.2 6.4 5.9": ["evn"], "9.6 1.4 10.2": ["beehived"], "14.8 19.2 13.5": ["atari"], "1.7 32.1 1.8": ["exceptionalist"], "8.6 -4.6 8.2": ["lawnmowing"], "2.5 2.1 12.4": ["preinaugural"], "7.8 9.4 20.3": ["mexicana"], "1.3 14.4 27.1": ["haulouts"], "14.9 2.2 31.3": ["dolloped"], "0.8 7.4 22.9": ["osteria"], "-1.5 7.8 -0.7": ["unextended"], "4.0 15.9 4.8": ["reeducated"], "2.3 -6.6 4.3": ["hrough"], "4.6 14.0 8.1": ["partaker"], "3.2 8.7 25.8": ["goosey"], "4.8 6.3 17.4": ["chromoly"], "-1.4 6.0 -4.0": ["dedicatee"], "-0.6 9.6 9.4": ["juris"], "-0.4 0.6 19.5": ["exactor"], "3.9 13.2 12.0": ["tetherin"], "8.7 3.6 26.3": ["supremes"], "8.7 9.6 12.2": ["utopic"], "10.0 9.2 10.5": ["microcircuit"], "-5.6 9.2 2.6": ["deannexation"], "-0.8 2.8 4.6": ["spen", "tical"], "14.7 27.3 0.8": ["uncaptured"], "18.1 29.1 9.0": ["malefic"], "8.8 16.6 10.4": ["sophist"], "-8.2 13.0 4.8": ["rebuttable"], "8.0 11.7 5.5": ["superfluids"], "-2.6 18.1 8.3": ["adlibs"], "12.4 3.1 23.7": ["leche"], "2.5 6.3 12.9": ["chlorate"], "9.8 10.0 31.7": ["sauteeing"], "13.4 7.9 5.2": ["bodyblow"], "9.4 9.4 30.9": ["gravid"], "1.6 2.7 -0.3": ["dexanabinol"], "5.6 4.2 3.9": ["hemostats"], "30.8 12.1 21.3": ["hourglasses"], "-3.8 -1.1 4.6": ["nonsteroidal"], "3.3 14.0 13.6": ["tyrosinase"], "-6.6 10.2 2.0": ["epeeist"], "11.3 16.3 4.6": ["cropduster"], "0.2 9.5 4.1": ["alowed"], "11.2 10.3 26.7": ["weigela"], "10.7 10.4 14.3": ["siheyuan"], "19.6 6.5 7.3": ["superkid"], "3.8 13.6 11.9": ["whatshisname"], "3.2 5.5 8.6": ["boardriding"], "8.1 23.9 3.2": ["thetan"], "8.1 4.3 13.2": ["tye"], "3.9 19.1 14.3": ["farmable"], "3.6 2.7 12.3": ["taxfree"], "6.5 10.3 15.2": ["trunklid"], "0.4 9.2 2.2": ["systematization"], "7.9 14.2 17.3": ["younguns"], "10.6 7.2 12.2": ["guestimates"], "4.6 11.1 -2.5": ["clubside"], "8.8 10.9 2.6": ["interntional"], "14.4 8.1 19.6": ["splattery"], "9.1 16.3 9.3": ["housebreaker"], "12.4 0.8 9.8": ["maintenant"], "7.8 15.5 15.8": ["officiousness"], "8.6 12.6 32.6": ["sooks"], "24.6 22.7 13.2": ["chainsawing"], "-0.8 7.6 -1.8": ["sagte"], "8.5 6.6 15.2": ["mando"], "26.7 24.8 21.3": ["kaiju"], "15.2 10.4 28.7": ["ammonite"], "9.2 2.9 18.5": ["binners"], "4.8 15.2 6.6": ["stingingly"], "1.5 6.8 9.9": ["toccata"], "8.5 8.8 27.7": ["glads"], "7.2 12.8 15.4": ["rikishi"], "22.6 21.7 22.7": ["blox"], "13.8 14.0 32.5": ["remora"], "17.4 18.9 18.3": ["dohyo"], "8.1 1.6 16.0": ["reeler"], "24.7 13.7 18.4": ["flubber"], "13.6 -3.1 3.6": ["onsold"], "5.9 1.6 16.9": ["coatdress"], "10.5 12.7 7.7": ["vga"], "-0.5 -2.8 9.7": ["ferromolybdenum"], "8.6 -1.0 16.8": ["pez"], "11.4 1.4 7.1": ["rebids"], "6.0 14.0 23.8": ["underpainting"], "5.4 18.4 14.2": ["phans"], "6.2 28.0 13.9": ["prophesize"], "15.6 16.3 8.2": ["numberpad"], "-5.2 1.1 6.9": ["liturgists"], "5.2 19.5 9.4": ["admonitory"], "1.6 16.2 25.2": ["leafhopper"], "2.0 2.7 4.7": ["departmentalized"], "0.9 6.8 9.7": ["mixdown"], "14.7 4.3 12.1": ["tambour"], "2.5 0.4 10.8": ["kailangang"], "6.3 14.5 8.5": ["synchronicities"], "14.8 5.5 37.4": ["butterbeans"], "23.0 18.6 20.3": ["hippopotami"], "7.0 1.6 8.4": ["euphoniums"], "-0.3 1.9 2.8": ["ank"], "6.4 1.8 5.3": ["mridanga"], "-3.3 4.6 18.3": ["kaibigan"], "3.5 7.7 17.2": ["snowkiting"], "10.8 1.4 24.6": ["koko"], "-0.0 6.0 9.4": ["revaccinate"], "4.1 11.0 9.8": ["healthly"], "2.6 1.6 5.8": ["notifed"], "-1.1 5.2 4.6": ["cpi"], "1.1 12.4 7.1": ["ligase"], "-6.9 7.3 12.6": ["requalifying"], "12.9 -6.3 7.7": ["hanno"], "16.0 -0.5 1.2": ["autoshow"], "12.6 12.9 18.4": ["lordy"], "0.5 16.2 14.9": ["aggravatingly"], "17.3 2.5 1.6": ["enterpreneur"], "8.2 0.6 13.1": ["doners"], "-2.0 5.1 1.2": ["ison"], "-6.2 -4.3 4.8": ["curren"], "-2.9 6.7 26.0": ["asafoetida"], "1.9 1.5 13.2": ["volar"], "10.1 19.4 11.4": ["mudholes"], "-1.0 6.9 5.3": ["siddha"], "8.6 4.6 13.0": ["atch"], "14.7 12.6 0.1": ["fanpage"], "13.9 3.2 9.5": ["pliancy"], "16.8 10.6 7.4": ["plutoids"], "16.0 8.1 43.3": ["eggroll"], "20.1 0.7 6.7": ["blocklong"], "4.1 17.1 0.8": ["fractionalization"], "10.6 6.5 6.7": ["parly"], "8.0 8.0 10.4": ["casualised"], "0.3 18.2 8.8": ["penality"], "18.5 9.8 11.9": ["afficianados"], "2.1 6.5 -2.2": ["archbishopric"], "1.3 3.7 11.9": ["alkyd"], "5.8 -12.3 -0.3": ["projec"], "8.1 10.3 15.2": ["mona"], "8.0 3.4 4.3": ["reimage"], "0.4 9.6 12.8": ["segregations"], "8.6 12.5 30.8": ["bluejays"], "0.4 5.2 8.8": ["hippocampi"], "16.9 7.9 14.2": ["moshed"], "12.8 16.8 5.5": ["babblings"], "16.7 11.8 28.5": ["comestible"], "7.4 2.8 6.5": ["iridology"], "1.2 2.1 -0.4": ["reas"], "20.4 3.2 31.0": ["ptd"], "-0.5 1.1 6.0": ["autogenous"], "-0.2 14.0 10.5": ["volatilization"], "-2.9 5.2 3.1": ["ttyl"], "6.2 2.8 11.7": ["polyphosphate"], "11.2 16.4 11.0": ["staving"], "10.7 5.9 12.3": ["showily"], "0.2 12.7 8.9": ["syringomyelia"], "9.1 15.2 13.7": ["multitool", "mollifies"], "-1.6 -5.5 9.4": ["kor"], "16.2 4.2 9.1": ["refillers"], "9.4 5.7 9.4": ["pluthermal"], "-6.6 2.1 6.1": ["hemiarthroplasty"], "13.2 8.0 20.6": ["scratchies"], "5.3 11.8 7.8": ["waisting"], "12.9 14.2 18.8": ["mcdonald"], "6.5 2.5 19.2": ["colourway"], "12.5 8.6 19.5": ["spinifex"], "-1.4 0.2 4.9": ["dwellinghouse"], "3.0 -2.0 8.9": ["rahk"], "1.5 6.5 12.7": ["boardinghouses"], "2.7 10.5 10.8": ["multiracialism"], "5.6 5.3 15.9": ["smokeout"], "12.4 4.4 17.6": ["hatband"], "2.5 6.3 10.9": ["theday"], "14.1 18.6 8.3": ["shutup"], "1.1 2.2 2.4": ["noncancer"], "11.8 9.6 2.9": ["recons"], "11.8 14.4 27.9": ["skeg"], "3.6 20.2 11.6": ["glanders"], "3.0 1.1 16.2": ["boardshort"], "22.2 8.9 23.0": ["yipped"], "-7.5 3.9 7.3": ["leucopenia"], "6.1 -0.4 20.4": ["muncipalities"], "12.6 16.5 12.0": ["plently"], "0.9 -1.1 -0.5": ["ceed"], "2.8 6.2 7.3": ["dhamaal"], "13.7 9.0 31.0": ["pearled"], "3.9 -0.2 7.1": ["eluting"], "9.1 23.2 13.4": ["fakeout"], "-3.3 9.2 6.3": ["retrogressed"], "-2.5 5.5 4.3": ["presbyopic"], "0.4 -0.2 7.1": ["groupage"], "-7.1 7.2 3.4": ["orchiectomy", "ardas"], "16.1 19.5 21.8": ["tickly"], "5.2 -9.2 8.9": ["reveiw"], "17.1 10.7 20.4": ["sheave"], "8.4 20.8 8.5": ["boringness"], "-5.5 -5.5 -1.4": ["eduation"], "30.1 15.2 13.2": ["thingys"], "18.3 14.1 30.6": ["punkin"], "13.3 8.4 11.6": ["unpassed"], "11.1 -2.1 16.3": ["ecolabel"], "-0.4 7.8 14.2": ["jazzer"], "-3.2 10.9 -8.5": ["inovia"], "12.4 35.7 10.7": ["bloodthirstiness"], "-1.2 13.7 7.6": ["uncharacterized"], "0.2 1.2 15.5": ["unang"], "6.6 26.1 21.0": ["wherewith"], "-2.2 8.4 3.8": ["actinides"], "1.2 3.6 3.0": ["tranfers"], "5.3 3.6 6.7": ["noodlings"], "12.4 19.3 18.0": ["dogcatchers"], "-8.3 5.1 7.7": ["exertional"], "5.2 2.0 8.9": ["hatting"], "9.5 4.4 20.2": ["shikara"], "2.6 10.0 1.6": ["asystole"], "1.3 8.3 1.7": ["outbraked"], "-6.1 5.1 2.2": ["premorbid"], "30.2 6.0 3.2": ["manufactuer"], "13.3 14.9 -8.8": ["theonly"], "17.4 9.4 18.8": ["footpad"], "10.3 10.5 12.3": ["moleskine"], "-7.5 12.5 2.6": ["rebbetzin"], "9.9 8.8 34.5": ["capicola"], "0.1 16.7 5.9": ["indifferences"], "3.5 20.6 -2.8": ["comprehendible"], "16.9 2.5 18.9": ["snowglobes"], "3.6 11.4 11.4": ["charterparty"], "10.7 18.0 17.5": ["isobars"], "4.2 2.9 9.0": ["liftback"], "19.7 3.3 30.7": ["taquito"], "-6.9 9.1 14.7": ["outcross"], "7.2 17.9 13.1": ["chargedown"], "11.1 19.0 13.2": ["churl"], "-6.2 6.5 7.2": ["unavailabilities"], "5.4 7.4 15.2": ["shoptalk"], "9.5 17.6 13.7": ["tatter"], "-4.1 12.2 -0.2": ["interferred"], "0.2 0.5 5.7": ["monroe"], "7.6 4.4 38.4": ["longans"], "-6.0 13.3 3.6": ["justiciability"], "7.5 17.0 5.4": ["historicist"], "1.2 14.8 1.5": ["misallocating"], "5.0 15.9 12.1": ["hometowners"], "9.9 13.3 6.8": ["bcuz"], "5.9 8.5 9.3": ["proteolytic"], "14.9 11.7 18.0": ["pubgoers"], "10.6 19.9 12.8": ["smilies"], "6.2 3.6 14.1": ["histoire"], "-0.6 18.9 11.1": ["outwrestle"], "6.5 11.2 9.3": ["swamy"], "-0.9 17.3 12.5": ["impracticability"], "16.3 11.7 3.2": ["soupnazi"], "10.1 28.9 15.2": ["newb"], "7.3 11.3 16.4": ["lamisil"], "7.2 15.4 13.4": ["drowing"], "17.7 12.7 20.1": ["dogshit"], "7.5 29.0 7.4": ["enfeeble"], "0.3 4.0 2.2": ["nworks"], "-0.8 6.8 13.7": ["kamnan"], "7.0 7.9 18.1": ["aquaporins"], "15.0 0.4 18.2": ["stringless"], "8.5 10.9 2.8": ["coralled"], "22.9 19.6 13.9": ["empyrean"], "5.0 3.9 2.0": ["primatology"], "5.4 6.5 14.6": ["nao"], "18.1 11.5 13.6": ["sidewinding"], "15.9 16.4 22.3": ["capstan"], "0.6 2.1 5.6": ["weatherability"], "1.8 2.5 -0.2": ["undercharge"], "8.0 4.2 10.9": ["runrate"], "5.2 14.7 28.7": ["cogon"], "5.8 2.4 10.0": ["arrestin"], "-1.1 14.4 6.5": ["adriamycin"], "-8.0 -7.8 -1.4": ["ols"], "19.8 12.0 19.3": ["spongelike"], "4.9 9.0 3.4": ["souces"], "6.9 -3.6 -2.2": ["expresed"], "5.4 -0.2 24.8": ["tangier"], "9.1 9.2 12.1": ["boobage"], "-1.5 9.6 -0.8": ["servitudes"], "4.1 29.4 4.1": ["preemptory"], "4.9 2.9 12.9": ["mish"], "5.5 7.6 13.9": ["oly"], "9.4 -5.7 1.7": ["vur"], "10.6 7.0 13.3": ["palletizers"], "14.0 6.8 25.6": ["cofferdams"], "0.5 8.5 9.0": ["djing"], "12.5 5.1 4.9": ["anchorwomen"], "1.7 7.2 -0.7": ["mesage"], "9.6 -2.5 21.3": ["brekky"], "-3.4 4.3 1.4": ["fould"], "5.4 12.4 10.0": ["odf"], "7.0 7.7 1.5": ["luminosities"], "-3.0 2.0 4.6": ["annuloplasty"], "-9.0 14.1 4.4": ["hyperarousal"], "7.0 7.7 6.1": ["unfilmed"], "8.1 8.6 7.5": ["ballack"], "13.9 13.3 15.8": ["tappin"], "-1.6 -1.4 3.9": ["overbillings"], "8.2 9.8 8.6": ["doorstopper"], "9.0 13.0 12.8": ["funning"], "15.5 7.2 13.9": ["headwrap"], "-5.3 -4.2 0.2": ["distric"], "2.3 6.5 8.0": ["greenstones"], "14.5 7.9 8.1": ["hyperconnectivity"], "3.3 9.5 1.4": ["ofthem"], "9.8 9.5 8.9": ["gadding"], "0.6 18.4 7.6": ["arrogation"], "-2.9 4.7 5.7": ["transection"], "4.7 0.9 15.2": ["eugenol"], "3.5 9.1 2.1": ["importuned"], "4.9 19.2 8.7": ["orgin"], "6.2 -1.7 13.2": ["martha"], "10.1 16.7 13.6": ["froideur"], "9.6 5.5 15.4": ["michele"], "9.1 19.1 5.9": ["capcom"], "5.6 17.0 15.1": ["strokemaking"], "1.0 10.7 10.9": ["stockouts"], "7.8 13.8 7.7": ["unobvious"], "11.0 19.8 26.8": ["jewelweed"], "10.6 15.5 3.8": ["themeselves"], "0.9 4.6 12.4": ["naya"], "7.9 -1.7 17.4": ["warmblood"], "-2.4 6.4 28.5": ["haenyeo"], "17.8 6.1 17.6": ["monobrow"], "11.0 6.8 4.1": ["manorial"], "26.6 14.6 12.5": ["posable"], "6.0 -8.4 10.2": ["dhs"], "-2.9 6.4 9.4": ["sulphidation"], "1.9 9.8 7.4": ["meprobamate"], "6.7 19.3 14.3": ["samsara"], "13.4 9.9 7.2": ["handycams"], "5.5 11.1 13.7": ["outstays"], "3.3 -4.5 1.7": ["ased"], "2.8 14.8 8.0": ["togather"], "0.8 8.5 5.1": ["rj"], "-4.6 5.9 6.4": ["rbis"], "8.2 11.1 8.1": ["polymorphs"], "0.9 11.6 6.5": ["hydrolyze"], "1.9 11.6 6.7": ["sicknote"], "-1.4 12.8 5.4": ["nucleate"], "-1.6 -4.2 9.4": ["kbp"], "14.9 4.6 8.1": ["trampolinists"], "9.8 14.2 9.1": ["mirrorless"], "9.6 0.2 20.8": ["hayes"], "22.1 10.0 17.8": ["pilferer"], "6.7 10.6 17.4": ["hindgut"], "2.7 12.9 9.2": ["feebate"], "13.8 13.2 22.6": ["sparrowhawks"], "8.5 4.8 10.9": ["myoblast"], "6.9 26.4 1.2": ["debkafile"], "5.1 25.1 15.0": ["gratuitousness"], "8.4 24.5 5.6": ["flashgun"], "2.4 9.0 11.3": ["mowings"], "1.3 7.6 16.0": ["ayaw"], "-0.6 3.0 21.0": ["eri"], "3.8 0.6 -1.3": ["monohydrate"], "2.4 6.7 -1.2": ["zwischen"], "14.3 15.1 15.9": ["shadeless"], "-10.7 8.8 8.8": ["perianal"], "14.0 0.5 3.3": ["rejuvenator"], "6.9 18.8 10.2": ["exhilerating"], "4.5 7.1 20.2": ["deckers"], "3.2 8.7 6.5": ["voto"], "3.6 9.2 8.5": ["amnion"], "11.1 15.1 7.0": ["ramified"], "4.6 4.2 25.1": ["vadas"], "6.3 1.1 8.3": ["ecclectic"], "4.4 1.5 31.1": ["appam"], "13.9 4.0 22.5": ["steet"], "6.3 11.1 2.2": ["wollen"], "-9.1 9.5 0.3": ["commissionerates"], "3.4 8.6 8.6": ["pinhooking"], "-0.8 11.9 6.2": ["tumults"], "5.3 15.2 6.6": ["retransmits"], "7.8 10.9 6.0": ["transportive"], "-4.4 11.9 17.2": ["runnable"], "-3.2 26.8 4.6": ["delegitimisation"], "4.6 10.8 11.9": ["coalbed"], "21.2 10.9 22.4": ["trammel"], "7.1 5.5 10.5": ["perecnt"], "9.3 6.0 17.3": ["ontogeny"], "-1.1 10.1 6.8": ["musicalized"], "-9.6 5.1 14.3": ["tuitioning"], "-0.8 -5.3 8.6": ["benzylpiperazine"], "7.7 9.4 11.1": ["homeowning"], "11.7 4.9 16.8": ["dala"], "6.7 5.8 27.3": ["loquats"], "12.9 0.5 2.7": ["loftlike"], "13.4 8.7 -4.8": ["worls"], "8.1 12.7 11.9": ["neve"], "1.6 10.0 10.9": ["unseparated"], "10.3 2.0 1.6": ["electronification"], "-0.6 16.2 12.6": ["subtasks"], "11.4 7.4 12.4": ["psychadelic"], "-2.1 1.2 12.4": ["shcool"], "-3.2 4.1 5.4": ["underspends"], "24.8 6.4 24.1": ["tiddly"], "1.6 12.1 26.2": ["haroset"], "9.5 26.8 8.7": ["repetitiously"], "-1.0 -2.5 3.1": ["selfemployed"], "17.4 6.3 22.3": ["carpetbag"], "13.9 11.2 7.0": ["lowlier"], "-9.5 0.8 0.8": ["ofwhich"], "16.0 3.8 25.2": ["porked"], "8.8 21.6 15.0": ["demesne"], "6.4 2.4 -1.3": ["equipo"], "-10.1 3.1 5.8": ["workcamp"], "15.4 9.8 19.2": ["stubbie"], "7.1 8.7 6.8": ["intragroup"], "-3.5 11.6 -9.7": ["mistreatments"], "7.7 18.6 14.9": ["chairshots"], "6.7 8.5 0.2": ["resettable"], "0.1 23.5 9.0": ["euphemized"], "15.4 1.5 35.8": ["langostino"], "14.7 12.6 23.4": ["dalmation"], "-2.2 22.4 10.4": ["playthroughs"], "12.0 10.1 23.1": ["rodders"], "16.8 -0.6 -0.8": ["deutschmarks"], "5.7 4.1 34.9": ["rambutans"], "-3.2 2.2 4.7": ["arthrogryposis"], "1.4 19.9 9.6": ["logorrhea"], "12.7 19.6 26.0": ["harpooner"], "-2.3 13.0 4.5": ["jaxtr"], "5.6 0.8 5.4": ["docuseries"], "16.4 16.0 5.3": ["unwieldiness"], "7.1 -0.5 -1.1": ["truetones"], "17.0 -3.8 26.4": ["enamelware"], "16.1 14.3 26.8": ["lopper"], "-0.2 11.1 15.5": ["amplicon"], "1.7 15.0 11.3": ["indignance"], "10.1 12.6 29.8": ["underripe"], "7.7 14.4 8.4": ["grandstanders"], "-1.2 16.7 7.6": ["deflations"], "11.1 15.8 12.6": ["outsidethesidelines"], "1.1 9.4 13.9": ["weighin"], "7.1 3.0 11.5": ["bunded"], "-4.7 6.8 6.6": ["bleedings"], "1.8 1.4 6.7": ["cryopreserving"], "11.9 7.1 17.9": ["stela"], "4.1 12.1 15.3": ["shure"], "2.6 -1.7 3.2": ["transactor"], "9.7 10.9 -0.6": ["scrobbling"], "-9.6 10.2 0.8": ["autobiographic"], "4.1 5.1 -2.5": ["unappeased"], "8.4 12.8 10.6": ["enterance"], "4.7 13.9 12.3": ["laxers"], "12.7 10.1 10.9": ["pornstars"], "13.4 24.2 15.8": ["banhammer"], "4.9 6.0 5.3": ["rekick"], "23.7 12.9 12.3": ["leakiest"], "7.8 -2.0 13.4": ["surance"], "8.4 19.6 18.2": ["waistlock"], "1.8 15.4 8.2": ["quarteback"], "14.8 3.2 18.4": ["vizsla"], "0.6 -0.2 17.1": ["mooseburgers"], "-8.2 0.4 6.4": ["prefiling"], "2.4 7.5 8.4": ["hectres"], "13.8 2.1 30.7": ["arroz"], "5.4 16.0 10.5": ["galavanting"], "17.3 4.0 15.1": ["carthorse"], "-2.1 11.6 8.6": ["inurned"], "3.0 9.3 0.8": ["concededly"], "7.3 5.5 25.9": ["guan"], "14.4 6.8 13.6": ["silkiest"], "5.4 11.2 13.3": ["goodery"], "1.9 -4.8 5.3": ["cofinancing"], "8.3 -5.4 1.6": ["halfshaft"], "8.5 10.2 8.4": ["tehy"], "-8.4 0.8 5.9": ["hepatologists"], "13.5 -3.1 3.5": ["starstudded"], "1.7 12.4 8.7": ["ministroke"], "5.5 13.9 8.0": ["gracelessness"], "0.9 8.0 14.1": ["klonopin"], "15.5 18.2 7.4": ["crapfest"], "1.0 12.4 11.7": ["rulesets"], "12.5 11.4 28.7": ["tubercles"], "7.2 31.9 8.9": ["metagame"], "0.8 11.1 9.2": ["ultramafics"], "5.5 8.6 31.9": ["passerines"], "-3.5 2.8 11.7": ["chieh"], "10.4 7.4 16.1": ["horseless"], "2.7 24.5 2.3": ["unscrupulousness"], "6.5 8.6 8.3": ["bandsaws"], "27.5 9.6 26.0": ["caldrons"], "5.7 2.8 11.2": ["hbo"], "11.2 -1.9 3.6": ["whichwas"], "-2.8 -8.5 -0.9": ["meeing"], "8.2 17.8 6.6": ["valorize"], "-2.1 1.2 8.1": ["ghall"], "-0.2 9.6 -1.2": ["regenerators"], "17.9 8.8 15.0": ["cartooned"], "11.5 2.6 12.8": ["landrush"], "-2.6 14.9 5.2": ["infibulation"], "-1.1 10.9 18.0": ["atall"], "14.3 8.3 15.5": ["meths"], "5.1 0.2 8.4": ["primness"], "15.9 15.4 6.8": ["unclenches"], "5.5 3.6 0.9": ["bodywear"], "8.9 3.4 19.1": ["junkanoo"], "12.3 11.0 12.7": ["gavage"], "12.3 12.5 22.5": ["lifebuoys"], "7.0 10.2 1.0": ["extraodinary"], "9.9 22.1 4.1": ["transonic"], "17.9 2.0 7.8": ["fundi"], "9.5 35.6 5.2": ["archvillain"], "12.6 6.6 12.4": ["punta"], "-2.7 10.8 2.4": ["macht"], "2.4 -8.6 7.2": ["igh"], "10.7 7.1 13.0": ["folksonomy"], "12.9 12.8 11.5": ["gimmicked"], "16.2 23.7 21.3": ["quaffle"], "5.6 5.1 16.0": ["brassier"], "13.7 -4.4 16.8": ["alberta"], "3.8 14.3 12.9": ["flurrying"], "-0.9 1.1 3.5": ["hobli"], "-7.3 17.4 -3.1": ["videoteleconference"], "3.2 3.8 10.0": ["palletizer"], "12.3 10.9 -3.1": ["oopsie"], "-7.8 -0.4 -2.4": ["khutbah"], "4.8 21.1 9.7": ["egotistically"], "3.1 -0.2 7.0": ["nq"], "14.1 3.3 11.5": ["strangehold"], "8.5 9.4 16.3": ["heatspreader"], "2.9 -2.6 0.7": ["availalbe", "lisdexamfetamine"], "22.2 14.1 8.4": ["chappies"], "0.3 7.3 7.2": ["surehanded"], "10.7 9.7 8.3": ["prelapsarian"], "11.0 6.5 18.5": ["mycological"], "8.8 17.5 6.2": ["strenth"], "8.3 12.7 10.2": ["occultations"], "-3.0 13.6 2.6": ["constructiveness"], "9.8 3.1 7.8": ["fea"], "0.4 7.7 3.3": ["anchorpersons"], "9.0 12.0 19.9": ["corrie"], "8.5 5.6 11.5": ["curtis"], "6.1 19.1 16.3": ["kimbo"], "3.2 10.8 8.9": ["amphibole"], "1.5 -3.9 4.2": ["togive"], "6.7 -1.3 8.1": ["peu"], "10.4 17.1 13.4": ["santorum"], "1.4 14.4 9.1": ["suposed"], "0.8 4.5 14.0": ["meclizine", "extempo"], "0.4 6.8 8.6": ["doublings"], "5.5 -9.9 -2.0": ["coproducing"], "15.3 11.1 22.0": ["rockeries"], "0.5 6.5 0.8": ["strenous"], "7.0 9.9 24.7": ["bhelpuri"], "0.8 1.0 3.6": ["nonpreferred"], "5.9 10.7 23.5": ["koji"], "11.5 21.8 15.8": ["engulfment"], "9.8 14.8 5.5": ["webservers"], "12.7 13.3 14.8": ["vietnamese"], "7.0 12.9 16.8": ["itsa"], "2.6 34.2 8.4": ["neocolonialists"], "4.5 20.1 8.8": ["empiricists"], "8.9 -1.3 7.9": ["dix"], "9.4 8.6 10.1": ["clasicos"], "20.1 17.7 21.6": ["doodoo"], "11.8 2.9 6.3": ["jsp"], "2.0 7.2 9.3": ["laterality"], "10.9 2.7 21.6": ["atole"], "14.5 12.9 18.0": ["jackin"], "12.7 4.0 10.1": ["tsavorite"], "7.6 13.3 -5.4": ["assumingly"], "6.6 9.3 5.2": ["whove"], "10.8 -4.1 7.3": ["tweetups"], "1.1 9.2 10.3": ["forgetten"], "1.9 7.6 -2.1": ["prudentially"], "7.2 25.5 12.8": ["ritualists"], "1.7 5.4 12.1": ["boleh"], "3.4 28.0 4.3": ["disunite"], "10.0 -2.9 2.7": ["settlment"], "6.3 12.3 4.4": ["inno"], "0.6 7.0 8.9": ["hilot"], "2.1 9.6 12.3": ["pronate"], "1.5 4.2 12.5": ["gentled"], "16.6 15.9 11.2": ["plonkers"], "11.1 -3.4 2.1": ["youthquake"], "5.9 0.2 9.6": ["talkfests"], "4.8 5.8 9.4": ["coppersmith"], "21.1 9.4 18.4": ["polly"], "10.2 4.0 19.0": ["cabochons"], "19.3 8.6 18.1": ["ankh"], "5.2 4.8 4.2": ["copperbelt"], "-1.9 5.2 11.9": ["explanted"], "8.0 17.9 20.9": ["venereal"], "7.8 4.7 5.4": ["nonenergy"], "4.6 -0.4 3.7": ["orthe"], "14.3 5.5 8.3": ["werk"], "3.9 6.9 15.8": ["horseshoer"], "-2.3 8.5 6.8": ["metis"], "2.2 9.8 8.9": ["teamsheets"], "5.8 4.9 7.2": ["placenames"], "18.6 20.1 16.2": ["winker"], "8.8 0.5 13.4": ["sacramento"], "3.7 9.0 10.3": ["hypochondriacal"], "-5.2 2.3 8.0": ["rela"], "9.0 1.8 2.2": ["schoolbuses"], "10.0 7.0 15.8": ["detangling"], "10.2 6.6 38.5": ["cacciatore"], "11.3 0.4 23.6": ["housecleaners"], "0.6 15.5 17.0": ["hamminess"], "14.9 6.5 13.5": ["dominatrixes"], "-5.6 4.8 -2.9": ["janaza"], "6.3 2.6 15.2": ["loob"], "7.3 8.6 3.7": ["innovational"], "7.7 6.7 14.9": ["deez"], "-5.5 4.5 5.9": ["inforamtion"], "-2.9 16.3 -6.9": ["abad"], "18.9 10.5 18.3": ["terrestial"], "2.4 1.0 15.8": ["maayka"], "7.2 7.7 8.9": ["wl"], "2.9 6.8 8.0": ["counterdemonstrations"], "7.5 15.5 9.2": ["youngs"], "9.6 10.0 14.1": ["dakota"], "5.5 2.4 9.2": ["machinable"], "6.2 18.0 2.6": ["charasmatic"], "22.3 1.0 16.7": ["eskies"], "0.8 6.8 5.5": ["indebtness"], "19.0 15.3 21.9": ["phlegmy"], "2.2 -0.3 13.9": ["leung"], "8.9 13.5 17.9": ["anticyclones"], "3.4 7.7 8.4": ["postbop"], "8.3 13.1 5.6": ["palmsolo"], "3.2 -2.6 14.3": ["deliv"], "5.7 10.6 9.8": ["countr"], "7.5 14.9 1.6": ["wideness"], "3.5 16.6 0.8": ["exaclty"], "15.4 13.3 9.3": ["perve"], "-6.0 20.0 4.1": ["protectee"], "13.4 4.0 12.9": ["scruffiest"], "7.6 7.3 8.1": ["redomiciliation"], "-0.7 0.8 12.3": ["cytokeratin"], "9.0 4.4 7.0": ["powershift"], "16.8 10.5 6.1": ["clasic"], "-1.2 -0.1 10.6": ["repavement"], "7.2 4.4 4.3": ["jersies"], "14.3 9.6 13.2": ["capsulated"], "-0.6 15.9 16.4": ["glovemen"], "-1.7 6.7 6.0": ["sofer"], "5.6 -2.1 17.1": ["backcombed"], "4.2 11.2 8.4": ["palmar"], "15.8 16.7 25.0": ["galah"], "7.4 18.4 18.1": ["somedays"], "8.9 23.3 12.6": ["stenches"], "0.1 5.0 2.1": ["misdating"], "10.6 4.7 6.6": ["subc"], "20.9 11.8 21.2": ["needlelike"], "10.8 14.2 18.6": ["beaner"], "4.3 5.1 15.5": ["koro"], "-1.5 8.2 3.3": ["masitinib"], "0.9 -0.0 -0.9": ["injurying"], "4.0 20.2 13.8": ["undesireable"], "-1.4 11.6 9.2": ["dlc"], "4.9 6.6 -1.1": ["havethe"], "-3.2 9.2 13.0": ["investitures"], "7.6 23.7 6.5": ["abjuring"], "5.1 6.8 1.1": ["kp"], "3.0 13.5 5.2": ["synaesthetes"], "4.7 -4.2 13.0": ["dros"], "9.9 17.0 8.4": ["reservedly"], "10.6 9.9 11.4": ["scenics"], "17.3 10.8 15.0": ["cartouches"], "7.9 10.7 31.6": ["pilau"], "4.1 7.2 38.9": ["weaks"], "15.9 17.5 31.9": ["kereru"], "14.5 1.9 16.8": ["nonrecyclable"], "2.4 -0.1 13.5": ["tered"], "17.3 26.5 15.5": ["eldritch"], "5.6 19.7 10.0": ["agelessness"], "-5.5 2.6 8.3": ["needlestick"], "9.1 0.9 6.4": ["revitalizations"], "-1.2 11.0 5.6": ["universalising"], "-1.9 12.9 10.8": ["detents"], "7.5 0.9 13.5": ["tercentennial"], "6.9 9.3 31.9": ["kinglets"], "7.0 14.7 12.2": ["grubbiness"], "3.8 7.8 -12.0": ["sucessor"], "-7.7 9.6 6.3": ["underdiagnosis"], "9.5 23.9 11.4": ["numbnuts"], "-2.7 8.4 14.6": ["thoda"], "12.5 5.5 8.7": ["electicity"], "0.8 6.1 2.1": ["enforcment"], "15.8 19.8 10.1": ["shhhhh"], "6.0 7.6 6.8": ["blushingly"], "-1.3 15.9 13.5": ["ceramahs"], "7.1 3.2 9.9": ["connexin"], "9.4 -0.0 13.7": ["sulkies"], "-0.6 3.6 10.0": ["cleanability"], "22.0 14.7 20.5": ["fenceposts"], "-0.8 16.7 16.7": ["fifer"], "-5.4 -1.8 6.5": ["nity"], "13.4 7.3 -6.8": ["cellity"], "3.9 17.8 12.6": ["progessive"], "5.3 15.0 -1.4": ["nyone"], "-5.2 19.8 3.8": ["eliding"], "2.7 5.9 7.6": ["jpgs"], "11.3 5.9 14.8": ["caroler"], "13.2 20.3 7.9": ["betokens"], "-7.7 1.5 8.0": ["limted"], "17.0 23.9 4.0": ["resurges"], "-0.7 6.5 11.2": ["transdifferentiation"], "12.0 5.2 17.4": ["hana"], "-1.8 0.2 13.3": ["postshow"], "8.8 3.8 9.4": ["hatmaker"], "1.4 4.5 19.0": ["dekha"], "-0.2 35.2 2.4": ["inteligence"], "-1.9 3.9 0.1": ["anastomotic"], "7.7 3.7 9.0": ["pourquoi"], "1.5 15.4 15.0": ["urease"], "10.1 10.3 7.6": ["acros"], "4.5 5.9 28.0": ["courser"], "3.9 2.5 5.8": ["proteoglycans"], "5.0 4.7 11.9": ["soulman"], "14.0 7.5 14.5": ["doss"], "-2.1 -2.6 4.1": ["ofstate"], "1.4 13.9 9.4": ["unsustained"], "16.4 -4.5 43.1": ["fishcake"], "2.4 6.4 3.4": ["kein"], "10.1 8.5 16.5": ["objet"], "2.3 18.3 27.5": ["hakapiks"], "-9.1 19.9 -2.5": ["unclarity"], "17.5 8.4 18.9": ["jivin"], "9.6 6.1 1.9": ["laninamivir"], "15.3 5.1 31.7": ["avo"], "0.5 13.0 -1.4": ["broadmindedness"], "18.4 9.0 20.0": ["fogbound"], "13.9 -2.9 15.2": ["racketball"], "6.8 -2.8 1.6": ["offfice"], "10.1 5.3 1.9": ["workcell"], "8.3 17.7 -3.8": ["stiffling"], "20.9 4.8 17.1": ["koru"], "22.1 17.5 12.4": ["sputnik"], "5.1 24.0 4.1": ["autosave"], "13.4 18.0 13.3": ["birdsongs"], "2.2 13.6 8.7": ["phoners"], "3.7 -2.7 20.2": ["mie"], "4.8 8.3 6.8": ["dispersible"], "2.0 7.3 12.6": ["hesperidin"], "6.0 21.9 12.1": ["truley"], "4.8 13.8 15.6": ["proteomes"], "12.2 -1.9 8.0": ["nighclub"], "4.2 12.1 14.8": ["zyxxy"], "17.0 12.4 13.4": ["dexter"], "9.1 4.9 16.4": ["pultruded"], "13.7 4.3 8.6": ["pharmacopeia"], "7.9 11.9 19.0": ["packhorse"], "3.5 13.7 7.0": ["invariance"], "-2.8 8.3 9.9": ["purok"], "7.2 6.9 33.3": ["birria"], "2.3 2.5 13.1": ["perahera"], "7.5 1.2 4.4": ["junto"], "8.5 -0.2 18.0": ["mbu"], "7.4 20.4 7.4": ["asingle"], "-2.2 3.2 3.1": ["adh"], "3.8 -9.8 1.3": ["presenta"], "-1.3 5.4 -0.2": ["backported"], "1.9 13.8 6.0": ["probabaly"], "-4.5 1.6 5.1": ["eme"], "4.7 -0.9 16.8": ["cannibis"], "5.3 3.6 9.7": ["taxe"], "-1.8 14.3 1.6": ["impeaches"], "8.7 6.0 3.9": ["repuation"], "17.2 6.7 -2.1": ["unsuccesfully"], "2.0 8.3 11.0": ["geochem"], "8.1 11.7 5.7": ["tripartism"], "3.6 3.8 7.8": ["vite"], "8.8 11.1 8.8": ["ecoterror"], "9.6 0.6 21.3": ["mbalax"], "5.8 14.7 3.4": ["intoxications"], "18.4 4.2 12.7": ["sellotape"], "14.4 8.2 5.9": ["bmg"], "2.5 3.7 23.6": ["tortie"], "-15.5 0.7 -3.1": ["aksed"], "6.5 5.6 1.9": ["neaclear"], "3.0 12.8 8.7": ["instantiations"], "20.1 10.0 -0.7": ["supercollider"], "6.1 16.6 12.6": ["thair"], "-1.2 -0.4 8.9": ["suo"], "-0.9 11.3 13.5": ["liverworts"], "-3.5 3.6 16.9": ["roussanne"], "10.6 12.8 8.0": ["mockable"], "9.3 6.8 -4.6": ["vaunts"], "0.3 25.4 9.7": ["rhetoricians"], "3.5 5.8 5.3": ["toplay"], "13.6 11.2 27.7": ["bluenose"], "17.8 5.2 13.5": ["rumbler"], "6.7 1.4 15.8": ["wea"], "9.4 15.3 7.9": ["incompetance"], "2.0 -0.6 -0.5": ["nightshifts"], "-1.5 10.4 1.4": ["etrace"], "4.6 7.8 16.0": ["doan"], "11.1 16.7 16.8": ["axions"], "9.6 16.0 10.9": ["otherworldy"], "7.0 7.2 16.4": ["reimposes"], "-3.9 15.7 3.1": ["thatwe"], "-1.4 13.7 11.7": ["ganda"], "8.0 9.4 25.0": ["kochia"], "-3.9 10.6 2.4": ["bedoons"], "9.6 27.0 2.7": ["unobjective"], "0.4 8.4 8.9": ["anomolies"], "1.7 -1.4 8.3": ["nonylphenol"], "4.7 0.2 8.8": ["resecuritizations"], "13.3 23.6 12.1": ["gripers"], "-3.5 12.0 1.5": ["sustainers"], "12.3 14.9 11.4": ["galvanization"], "4.8 18.2 20.6": ["limpers"], "-6.4 18.0 1.8": ["observables"], "6.6 -0.3 14.4": ["funday"], "9.1 13.4 7.4": ["unbuttons"], "0.1 10.4 11.8": ["lockin"], "0.2 5.0 0.5": ["levosimendan"], "7.5 0.7 9.4": ["wm"], "18.1 10.1 22.2": ["hornpipe"], "2.7 10.3 5.8": ["psia"], "2.6 9.0 16.5": ["hindbrain"], "12.3 2.2 7.3": ["retiled"], "9.6 14.8 15.4": ["legbreak"], "7.2 3.4 17.0": ["bodyside"], "-1.0 4.1 7.1": ["ech"], "11.5 13.2 21.3": ["piehole"], "-3.9 1.1 -5.8": ["whohave"], "16.2 17.6 12.5": ["dominants"], "22.4 18.9 29.4": ["crinoids"], "28.2 16.2 44.5": ["isopods"], "-8.5 0.3 10.8": ["betamethasone"], "9.5 12.8 16.5": ["cathedra"], "-1.0 9.9 8.3": ["duniya"], "17.6 15.0 19.7": ["calderas"], "0.3 2.6 0.9": ["einmal"], "5.2 7.5 16.0": ["chala", "laddy"], "6.3 4.4 12.3": ["drifty"], "-0.6 -2.3 5.9": ["ined"], "8.2 18.4 5.9": ["acquirors"], "12.4 7.9 8.4": ["stimulous"], "6.3 4.8 11.9": ["podocytes"], "-3.7 12.4 6.0": ["descrimination"], "6.7 5.2 2.6": ["airbuses"], "-6.6 6.4 -0.7": ["photodisinfection"], "10.3 6.4 16.7": ["spi"], "1.7 -0.0 15.3": ["travis"], "15.3 15.3 1.5": ["fundis"], "4.3 4.8 2.2": ["conserver"], "10.6 10.0 13.8": ["sunbathes"], "6.5 4.2 7.2": ["deisel"], "2.9 6.7 10.5": ["unicity"], "2.4 6.6 2.8": ["belaboured"], "7.1 -1.7 0.8": ["dunhill"], "5.1 1.0 -0.3": ["reedited"], "8.5 11.3 5.5": ["neighorhood"], "8.5 8.8 5.4": ["ultrawide"], "15.7 9.1 22.8": ["floorshow"], "8.0 13.8 9.6": ["underskilled"], "-5.5 2.2 -2.8": ["revalidating"], "3.4 6.3 0.3": ["respirable"], "7.4 8.8 6.6": ["piezoresistive"], "9.5 9.8 16.2": ["singulation"], "18.4 15.3 15.3": ["beatifically"], "3.9 5.8 6.8": ["ryol"], "-0.3 7.8 1.9": ["dysarthria"], "14.1 5.8 14.7": ["enamelling"], "3.1 2.6 11.0": ["avaible"], "-1.3 7.7 8.2": ["flaviviruses"], "9.8 3.1 11.2": ["silkscreening"], "-0.2 7.9 -5.7": ["prejudgement"], "9.1 2.4 15.2": ["farriery"], "-3.0 1.1 6.1": ["butene"], "13.5 10.0 7.1": ["longdistance"], "4.9 2.8 8.0": ["claddings"], "12.1 12.1 -1.2": ["skobbler"], "15.7 17.7 20.7": ["baaaad"], "1.4 7.4 -1.4": ["systole"], "4.6 10.3 6.5": ["allgedly"], "9.8 -2.9 26.6": ["gow"], "9.7 8.0 0.7": ["unbankable"], "13.6 -1.1 13.8": ["ropin"], "2.6 6.5 10.1": ["lettable"], "13.9 11.2 29.4": ["cockscomb"], "-1.9 1.8 7.6": ["plantilla"], "-7.4 1.6 3.8": ["bookwriter"], "1.9 0.4 10.0": ["backrubs"], "11.1 12.7 14.2": ["facewash"], "5.9 16.9 14.1": ["handpasses"], "-5.8 9.2 3.6": ["baselined"], "0.2 3.0 6.7": ["accts", "hydrolase"], "7.0 10.1 11.5": ["somethng"], "17.4 13.5 9.4": ["sanitiser"], "0.5 15.8 6.9": ["ungallant"], "-0.2 4.2 8.7": ["nuestro"], "3.8 7.3 15.7": ["bestfriend"], "1.7 13.7 3.9": ["karachi"], "4.8 -0.6 -1.9": ["thehighest"], "6.9 7.8 4.3": ["sincethe"], "5.9 3.9 12.3": ["liam"], "18.7 9.6 12.9": ["huckstering"], "14.9 16.9 11.8": ["hoopin"], "-3.5 0.5 4.3": ["bioidenticals"], "3.7 -0.2 20.8": ["kain"], "2.6 3.2 2.6": ["popliteal"], "10.2 13.0 13.2": ["gansta"], "-1.0 6.0 -2.2": ["rindopepimut"], "12.5 9.4 4.7": ["terascale"], "6.7 17.3 5.6": ["freescoring"], "17.8 26.9 10.8": ["unsheathing"], "7.7 5.3 7.0": ["otto"], "21.5 3.6 12.1": ["bakehouse"], "-5.3 18.6 8.1": ["winable"], "20.5 4.8 8.9": ["biros"], "7.4 2.6 23.2": ["sternwheelers"], "8.3 0.6 3.2": ["laryngoscope"], "-2.5 -4.2 -0.4": ["torney"], "8.6 3.5 5.5": ["transpromotional"], "4.7 14.5 2.3": ["himelf"], "16.0 11.5 6.5": ["wembley"], "9.6 12.1 29.4": ["ghillie"], "7.9 4.6 6.1": ["cx"], "5.7 9.1 3.6": ["affort"], "-9.3 8.0 -4.0": ["repairability"], "-7.1 7.3 5.4": ["alexithymia"], "8.8 17.6 6.3": ["ululate"], "1.6 7.9 13.7": ["oestrus"], "-2.3 3.9 8.8": ["vasodilatation"], "15.4 17.8 23.7": ["protozoans"], "1.4 7.1 14.6": ["scopey"], "13.0 16.0 24.3": ["fucken"], "15.8 6.9 4.8": ["springboarding"], "14.2 -10.3 -5.5": ["anounces"], "0.9 5.0 3.9": ["cediranib"], "9.9 6.9 11.5": ["understructure"], "7.7 8.4 16.8": ["urbanise"], "0.9 0.3 9.9": ["anos"], "9.7 17.3 14.6": ["castrates"], "11.7 19.8 5.0": ["informationization"], "0.8 27.6 6.3": ["distractors"], "18.8 3.1 6.1": ["optomechanical"], "12.9 10.0 19.9": ["crushproof"], "3.0 13.1 8.2": ["chemosensory"], "-0.9 13.1 2.5": ["economizes"], "1.4 6.4 -4.5": ["neben"], "6.0 10.9 17.7": ["oligodendrocyte"], "11.0 6.8 10.4": ["unsated"], "28.2 -2.6 6.4": ["pipemaker"], "12.1 -5.8 4.3": ["bioindustry"], "10.9 -0.3 16.2": ["thenational"], "16.7 12.3 17.6": ["wrinklies"], "6.4 15.1 6.4": ["simulant"], "-5.1 1.4 7.4": ["arangetram"], "8.5 11.5 9.8": ["beatifies"], "5.6 8.6 11.0": ["unusualness"], "8.6 6.6 7.1": ["volvo"], "-6.9 1.3 10.5": ["attendings"], "3.2 10.4 14.2": ["giong"], "7.2 15.6 26.0": ["virginiana"], "-2.7 6.9 2.3": ["stylet"], "8.4 3.6 13.5": ["receeding"], "18.1 8.6 14.5": ["playgirl"], "24.5 29.8 4.4": ["multifront"], "3.1 -2.1 7.6": ["propionate"], "6.0 8.2 -0.7": ["hydrofluorocarbon"], "15.6 11.9 24.2": ["bellflower"], "1.0 -0.2 6.5": ["organisors"], "17.2 14.5 12.3": ["torrenting"], "-2.1 4.3 3.0": ["suffragan"], "8.1 15.0 8.6": ["atmopshere"], "0.8 8.5 7.4": ["polygenic"], "14.0 4.1 19.2": ["spandrels"], "-6.7 4.7 -0.6": ["ency"], "9.9 8.0 7.5": ["hoohah"], "7.9 5.9 2.1": ["spectrographic"], "1.1 -7.9 12.4": ["deadlifted"], "10.2 18.3 19.5": ["bullrush"], "-3.3 16.4 2.9": ["motivationally"], "10.6 13.7 14.5": ["caseback"], "-6.6 -1.1 6.1": ["minimun"], "1.2 12.5 16.9": ["wettability"], "-3.5 5.8 11.1": ["meditational"], "3.2 8.0 15.0": ["sphingolipids"], "12.7 21.3 11.5": ["insipidly"], "11.3 5.7 6.6": ["displayable"], "16.0 12.1 38.5": ["unripened"], "28.0 6.8 -5.2": ["aglobal"], "-1.7 14.3 8.4": ["dadi"], "14.0 6.5 6.1": ["newlook"], "5.2 9.5 3.7": ["viel"], "8.4 11.7 11.7": ["ingenius"], "9.0 23.1 13.6": ["overeagerness"], "3.8 7.3 10.2": ["unitaries"], "2.2 9.0 15.2": ["droney"], "11.8 5.9 16.8": ["quainter"], "11.8 5.2 4.4": ["gladhanding"], "-2.5 8.7 6.3": ["inspiratory"], "8.9 11.5 19.6": ["bunraku"], "13.9 5.7 13.7": ["jitterbugged"], "7.1 6.7 4.2": ["constrast"], "0.3 13.0 7.5": ["pithier"], "17.3 3.1 15.3": ["djembes"], "3.7 6.1 8.8": ["maharani"], "10.4 17.5 23.0": ["chimineas"], "9.1 25.2 14.6": ["gunny"], "8.9 19.2 12.0": ["vagary"], "10.9 16.0 12.8": ["amonst"], "6.4 0.7 35.0": ["cremini"], "-4.2 -6.9 -1.4": ["committals"], "1.2 19.4 3.3": ["reactance"], "4.3 -0.3 7.6": ["uptakes"], "15.4 12.2 25.5": ["carryin"], "7.4 -13.9 -4.5": ["niversity"], "0.6 7.5 10.2": ["juventus"], "10.2 15.8 13.6": ["gobbets"], "0.2 9.5 6.6": ["sexperts"], "8.7 8.2 11.1": ["epos"], "8.7 9.8 44.1": ["limu"], "-4.4 5.4 -1.4": ["incompliance"], "7.8 4.9 0.2": ["pipline"], "-7.2 2.5 5.5": ["pyridoxine"], "4.4 14.2 14.9": ["slabbed"], "18.7 4.2 14.8": ["teriffic"], "-5.1 2.1 13.4": ["semiregular"], "0.1 2.1 4.5": ["eurosystem"], "5.7 4.5 2.1": ["omnibuses"], "-7.1 4.6 3.4": ["enstooled"], "8.3 11.0 38.8": ["cutbait"], "2.2 20.9 4.8": ["infantilize"], "2.0 2.3 11.8": ["grt"], "14.5 9.9 21.7": ["indention"], "22.1 1.1 2.4": ["operater"], "-1.5 -2.6 12.6": ["sbdc"], "9.9 9.2 16.6": ["starching"], "14.0 4.9 11.7": ["novell"], "7.3 -3.0 35.7": ["fettucini"], "14.4 7.3 15.9": ["gaiter"], "-1.8 8.1 3.4": ["tuberculous"], "4.3 11.6 18.9": ["spirochetes"], "2.9 -0.5 13.3": ["huei"], "2.2 14.2 5.9": ["demagnetized"], "1.2 20.4 7.9": ["confrere"], "11.0 12.4 9.7": ["kickabouts"], "-2.2 3.5 -1.0": ["conection"], "1.4 10.2 11.3": ["propylitic"], "10.3 22.5 9.0": ["monstrousness"], "10.2 9.8 10.6": ["hieratic"], "1.8 9.4 13.7": ["sema"], "-2.8 26.7 -0.7": ["overmatching"], "1.8 1.7 6.0": ["maleate"], "0.4 5.1 9.2": ["kingston"], "-1.1 4.3 30.6": ["secondi"], "5.0 2.0 0.3": ["diathermy"], "18.4 8.1 24.2": ["encrust"], "13.0 -6.3 1.4": ["billionin"], "1.3 5.5 6.4": ["inothernews"], "-1.1 -2.0 21.6": ["futurities"], "11.1 2.5 13.4": ["tailwhip"], "13.2 7.2 7.5": ["decontaminates"], "20.9 5.1 12.9": ["colliers"], "15.4 3.3 1.7": ["joojoo"], "4.4 6.9 3.5": ["alexas"], "0.1 -0.3 8.8": ["bookclub"], "6.0 -1.4 9.8": ["estado"], "9.5 3.0 13.6": ["tabacco"], "-6.3 8.7 1.0": ["ert"], "-1.4 8.6 10.6": ["debonding"], "6.8 7.8 11.9": ["sabe"], "3.7 12.0 39.4": ["barbless"], "9.7 3.1 13.2": ["thas"], "0.8 2.2 10.8": ["investability"], "10.5 0.8 15.6": ["haircutter"], "10.3 3.7 25.5": ["crispbread"], "0.5 20.7 -3.6": ["communalised"], "12.8 -0.8 -2.4": ["particpation"], "16.1 6.1 19.5": ["superball"], "18.3 11.0 21.1": ["boof"], "9.5 10.9 10.7": ["bachao"], "-3.9 9.6 2.8": ["inapplicability"], "3.2 -0.3 -0.8": ["nebulisers"], "9.3 6.9 3.2": ["adapation"], "18.2 14.1 21.5": ["stipple"], "13.6 18.3 12.4": ["merica"], "1.5 16.8 9.6": ["hormesis"], "18.6 8.9 8.1": ["millons"], "16.4 13.3 10.0": ["overlit"], "-0.0 7.6 29.5": ["rapeseeds"], "-2.5 8.8 14.8": ["toni"], "8.0 17.8 14.5": ["bacterias"], "-2.3 -6.3 1.3": ["chare"], "13.3 1.7 17.1": ["reverbed"], "-0.9 14.4 0.2": ["humanrights"], "2.5 2.1 3.4": ["previs"], "0.7 6.3 -2.8": ["tachographs"], "10.9 17.1 2.4": ["recognizer"], "1.5 18.9 -0.3": ["ingrains"], "10.3 8.0 19.6": ["triste"], "8.0 20.7 8.2": ["fogeys"], "2.4 8.2 7.2": ["tollpayers"], "6.3 9.0 5.9": ["ventilates"], "6.7 8.1 5.9": ["fluoroscope"], "8.3 24.7 9.6": ["fornicator"], "-6.2 18.2 2.2": ["intendment"], "9.2 -5.1 -0.6": ["propsal"], "8.6 17.6 14.5": ["doorjambs"], "11.9 12.1 10.2": ["dinkum"], "6.4 13.7 14.8": ["whereon"], "4.9 7.6 11.5": ["mimi"], "-0.1 9.1 11.9": ["counterflow"], "1.3 20.2 -3.3": ["secularise"], "9.1 9.7 5.6": ["buildin"], "-0.4 9.6 12.8": ["mond"], "1.3 4.7 12.4": ["kwaso"], "4.3 19.8 10.0": ["anicut"], "11.2 16.0 17.6": ["perambulation"], "9.2 6.4 8.5": ["chalcogenide"], "4.4 20.1 0.7": ["desensitising"], "13.3 5.9 16.9": ["chunkiness"], "-3.4 3.9 17.4": ["glycolic"], "-2.2 9.9 11.7": ["mastocytosis"], "-0.4 27.1 6.6": ["embedment"], "4.2 5.1 21.8": ["manageably"], "8.7 22.3 4.6": ["vilely"], "6.7 3.6 12.5": ["spitballing"], "8.5 21.1 3.7": ["euroskeptics"], "-3.6 0.8 18.1": ["bestball"], "4.5 2.0 8.4": ["cheon"], "5.7 -1.5 19.7": ["susu"], "-2.9 1.6 0.6": ["uner"], "7.7 9.5 2.6": ["tenability"], "18.3 6.9 17.0": ["scoria"], "8.3 6.2 7.8": ["arformoterol"], "4.5 10.3 9.1": ["quizzers"], "16.5 0.5 12.0": ["popchips"], "24.3 8.9 14.4": ["bulgy"], "1.5 10.9 0.7": ["equityholders"], "3.9 15.3 8.5": ["anthelmintic"], "1.2 -4.1 3.3": ["suhn"], "-7.4 13.6 1.6": ["behoved"], "2.6 -1.4 4.7": ["grammage"], "6.9 14.5 12.4": ["defensin"], "2.2 3.0 10.6": ["bioidentical"], "6.6 12.3 26.2": ["afikomen"], "5.2 -5.1 -1.7": ["imbee"], "9.3 17.7 15.1": ["frontin"], "6.2 -0.6 16.5": ["rustically"], "2.0 9.6 21.7": ["balladic"], "8.0 18.1 8.8": ["homogenise"], "10.3 10.9 17.7": ["degrease"], "8.7 17.2 6.8": ["fireguard"], "8.3 22.7 8.2": ["unspotted"], "8.4 24.0 9.3": ["horsewhip"], "6.1 13.4 11.1": ["tantriks"], "0.4 13.4 27.6": ["barbecuer"], "15.4 11.7 14.4": ["agflation"], "0.4 4.2 5.6": ["delcared"], "18.6 17.3 17.9": ["cloven"], "2.4 11.8 12.0": ["drewishdrewid"], "7.2 5.6 16.4": ["abuelita"], "-7.8 9.4 -1.0": ["responed"], "4.9 28.3 -2.5": ["highjackers"], "0.1 5.2 7.6": ["yeat"], "9.2 8.8 18.5": ["metazoan"], "14.3 7.8 32.6": ["floret"], "9.3 -1.6 3.1": ["motorshow"], "-4.0 1.8 -5.4": ["biventricular"], "13.5 5.6 15.4": ["drumheads"], "12.5 8.4 13.8": ["crummier"], "20.5 8.6 15.8": ["kazillion"], "0.0 16.8 19.4": ["downlines"], "19.1 1.5 17.0": ["coffered"], "-5.3 -3.9 8.4": ["impro"], "6.3 13.5 11.6": ["chartplotters"], "11.7 4.3 7.6": ["veel"], "8.4 2.3 9.1": ["pixieish"], "1.3 27.8 -3.3": ["premeditatedly"], "4.3 13.0 25.4": ["dolma"], "3.3 15.8 26.5": ["coelacanths"], "6.7 15.6 10.1": ["catastrophies"], "4.3 13.5 9.6": ["forwardness"], "5.4 25.4 2.2": ["nonbelief"], "0.0 1.8 -5.9": ["organsiations"], "3.5 13.5 2.3": ["panchanama"], "8.8 12.0 12.4": ["mammies"], "2.6 13.4 16.6": ["triclopyr"], "10.4 16.1 5.8": ["hesistate"], "2.9 5.7 -3.7": ["distraint"], "1.6 14.3 6.9": ["puerility"], "14.5 14.3 19.4": ["cyclopamine"], "8.1 17.4 13.4": ["lunkheaded"], "-0.1 2.4 10.5": ["gyeong"], "3.8 16.1 16.7": ["symbioses"], "4.5 8.6 14.9": ["teenhood"], "-2.0 8.0 -6.0": ["invigilate"], "4.9 0.6 6.3": ["mometasone"], "-8.1 3.6 9.0": ["acco"], "3.6 28.0 20.0": ["thickheaded"], "9.2 1.1 9.4": ["uncatalogued"], "3.8 11.0 7.4": ["naqba"], "4.3 13.8 11.2": ["coloristic"], "-5.5 17.4 5.5": ["determiners"], "15.7 19.6 19.9": ["asterism"], "17.8 21.8 12.2": ["unbent"], "2.5 3.9 13.7": ["patronages"], "-2.1 16.7 2.0": ["refuelings"], "4.8 11.8 10.3": ["dwi"], "-12.8 1.3 -0.2": ["assited"], "3.9 8.1 1.4": ["numerable"], "14.8 15.2 16.1": ["superkicks"], "4.9 4.1 6.1": ["restabilize"], "8.0 -4.5 15.5": ["albany"], "6.0 7.9 13.0": ["lipofuscin"], "9.5 -3.1 5.1": ["litai"], "12.7 15.7 13.8": ["hyperboles"], "23.6 5.7 7.0": ["firma"], "-18.3 9.6 2.6": ["deputization"], "9.3 16.0 16.9": ["gooseflesh"], "4.4 10.5 19.0": ["grea"], "10.8 8.3 22.7": ["razored"], "15.5 12.1 16.9": ["rotoscoped"], "2.0 1.7 0.9": ["rescaling"], "2.1 11.0 16.1": ["castable"], "11.7 7.9 22.7": ["bascule"], "9.4 7.7 10.9": ["cordillera"], "17.8 4.0 -0.5": ["watercoolers"], "10.5 23.7 8.5": ["paranoias"], "5.1 17.8 1.0": ["solecism"], "1.4 5.8 8.4": ["backpoints"], "12.1 21.8 4.8": ["duplicitously"], "3.3 3.9 8.0": ["aying"], "9.1 4.2 10.7": ["toptable"], "2.7 5.7 11.4": ["nonjury"], "1.4 13.3 8.8": ["wilfulness"], "11.0 11.6 13.0": ["pogs"], "13.3 16.5 11.9": ["unwonted"], "-1.9 0.4 -0.5": ["appro"], "-0.1 -0.9 3.9": ["anterolateral"], "-2.3 23.3 3.4": ["orientalists"], "17.1 -1.0 10.7": ["cambridge"], "-6.6 7.8 10.9": ["thees"], "8.6 14.2 9.1": ["maidservants"], "9.9 21.3 20.6": ["bluelines"], "5.4 9.3 7.3": ["combinatorics"], "4.3 14.4 6.2": ["succintly"], "-1.6 11.3 1.0": ["butit"], "4.6 6.9 14.4": ["handyperson"], "9.8 12.5 6.8": ["seee"], "4.6 1.6 -0.6": ["successorship"], "-0.1 -2.7 0.8": ["thawte"], "15.5 10.3 26.7": ["cowries"], "8.5 2.1 12.8": ["wallyball"], "8.0 2.3 33.0": ["dijon"], "19.7 9.7 18.6": ["berimbau"], "11.1 21.0 -0.0": ["histroy"], "2.3 4.6 0.6": ["phion"], "7.5 8.7 8.0": ["downconversion"], "-0.9 4.6 12.8": ["puks"], "12.2 0.2 36.8": ["choux"], "3.9 9.3 11.2": ["fieldgoal"], "7.6 11.7 14.8": ["barton"], "10.2 5.4 9.4": ["patchier"], "7.8 22.3 5.9": ["anonymizer"], "11.9 9.2 10.3": ["hepcat"], "11.9 19.0 16.4": ["fakest"], "20.8 8.1 13.0": ["panpipes"], "4.6 6.2 3.8": ["absented"], "0.0 0.4 1.4": ["ovr"], "18.4 21.1 12.4": ["wimpiest"], "10.9 -4.4 25.9": ["fruitwood"], "3.0 7.9 3.3": ["notamment"], "6.6 19.8 1.0": ["marxism"], "1.0 7.8 16.1": ["dawson"], "-0.2 -0.7 4.8": ["larious"], "15.0 6.1 10.0": ["portacabin"], "17.4 12.5 28.9": ["dicer"], "2.6 3.6 5.7": ["admeasuring"], "-0.9 9.8 8.7": ["outlanded"], "6.0 25.0 8.5": ["motherlands"], "-3.8 3.7 -2.0": ["leukotriene"], "-5.7 10.6 2.1": ["naib"], "-4.8 11.7 3.4": ["honourables"], "20.7 16.7 28.7": ["burrowers"], "8.3 20.9 14.8": ["shapeshift"], "6.6 13.6 14.4": ["insurmountably"], "3.4 19.0 16.2": ["lungworm"], "13.7 9.2 13.1": ["lamella"], "-1.1 9.2 8.5": ["cohabitees"], "12.0 17.3 11.1": ["terawatt"], "18.5 17.8 4.7": ["supersmart"], "11.7 1.7 22.0": ["balsams"], "-0.1 8.6 15.7": ["convivium"], "7.1 7.8 19.6": ["jathropa"], "0.1 -1.5 11.8": ["snapshotting"], "12.2 11.8 22.1": ["parthenogenetic"], "1.2 3.2 5.6": ["parallelizing"], "3.2 14.3 7.8": ["synchronistic"], "-7.9 2.1 9.9": ["consulta"], "9.8 24.3 13.5": ["machos"], "-3.4 14.3 7.7": ["medicalize"], "24.7 20.5 14.1": ["gnomish"], "10.1 16.0 19.6": ["nanostars"], "-6.4 9.6 1.1": ["chaptered"], "6.4 3.3 8.0": ["gencos"], "0.2 4.5 13.9": ["unreduced"], "10.3 6.6 10.3": ["antiquarians"], "-0.1 13.5 4.4": ["possiblility"], "-6.0 -1.6 3.7": ["rhinoconjunctivitis"], "7.3 12.4 14.8": ["somebodys"], "14.1 17.4 28.2": ["hooved"], "4.8 12.8 11.0": ["superfluously"], "6.6 13.0 12.2": ["tither"], "9.8 20.8 14.6": ["boyos"], "8.5 9.8 11.1": ["reface"], "5.8 18.5 9.4": ["untraveled"], "9.9 8.7 13.7": ["beelines"], "23.0 18.6 12.6": ["nanomachine"], "18.2 -0.2 39.6": ["laver"], "9.3 18.1 14.4": ["orderonlineviagra"], "10.3 13.3 14.1": ["clathrate"], "7.3 21.4 29.6": ["sawflies"], "7.4 9.6 8.1": ["calendrical"], "-7.3 -6.1 16.7": ["simulcasted"], "30.7 18.7 19.8": ["splatting"], "19.7 0.5 18.3": ["upthe"], "5.9 4.5 -6.2": ["astrong"], "1.4 2.2 16.6": ["tripleheaders"], "12.5 -6.2 15.2": ["ehz"], "10.5 8.1 9.5": ["moonwalkers"], "-2.0 18.8 0.0": ["exculpating"], "0.4 23.3 11.5": ["overprotect"], "-0.6 1.0 12.6": ["downticks"], "7.9 10.1 8.5": ["undoctored"], "20.8 23.9 18.1": ["depthless"], "16.3 11.1 13.8": ["pittances"], "11.5 19.2 16.7": ["etymologists"], "8.1 17.9 22.5": ["petiole"], "0.9 7.2 5.1": ["unaffiliateds"], "-6.1 12.6 10.0": ["lymphocytic"], "7.6 16.0 30.2": ["bancas"], "14.6 10.5 0.9": ["yammered"], "11.3 6.8 5.7": ["smartens"], "2.7 7.3 5.5": ["discoursed"], "5.5 23.6 8.0": ["wheedles"], "-4.4 21.4 2.9": ["factionalisation"], "15.1 14.0 16.1": ["untwisted"], "5.9 11.2 16.8": ["spirts"], "6.9 9.6 5.3": ["surat"], "-5.6 17.7 2.0": ["interventionalist"], "-1.5 2.9 1.4": ["hungerstrike"], "-1.1 9.9 14.1": ["unadjuvanted"], "5.3 14.9 16.4": ["gopis"], "10.0 -2.6 8.6": ["rennovation"], "12.4 14.5 22.3": ["monkshood"], "-4.2 13.7 9.4": ["penances"], "6.4 6.1 -1.3": ["midwifing"], "5.9 10.7 9.6": ["restfulness"], "8.7 -2.3 9.9": ["edinburgh"], "3.0 15.9 12.5": ["tuffaceous"], "20.6 8.9 7.6": ["entrace"], "8.8 -1.1 0.2": ["reimplementation"], "5.4 8.3 0.5": ["thebusiness"], "3.1 16.9 16.2": ["lanthanides"], "4.7 7.3 18.9": ["simpsons"], "0.9 9.5 -2.8": ["accessability"], "11.5 5.2 3.2": ["hundered"], "6.4 -1.4 4.3": ["appartments"], "10.5 5.0 21.5": ["calif", "sunbonnet"], "2.2 3.2 14.5": ["noma"], "10.0 0.3 14.4": ["cartful"], "8.9 19.9 2.2": ["themsevles"], "19.2 16.4 30.9": ["redback"], "9.0 19.5 7.2": ["strikebreaking"], "9.1 -0.5 3.2": ["consumated"], "3.0 2.3 12.5": ["puwedeng"], "0.5 -0.4 2.6": ["acomprehensive"], "6.9 23.1 4.8": ["powerfulness"], "5.4 13.1 17.9": ["simpers"], "1.6 16.0 2.0": ["taximen"], "-0.5 10.9 7.5": ["exwife"], "15.0 12.4 8.9": ["relayers"], "18.0 23.6 6.7": ["garrotte"], "2.0 15.7 2.0": ["organziation"], "13.9 7.7 15.7": ["foolscap"], "-14.5 14.7 1.5": ["brevet"], "-5.4 -0.0 7.5": ["timepoint"], "4.1 8.4 13.8": ["choroid"], "25.8 3.5 21.6": ["tassled"], "3.3 16.7 0.1": ["passingly"], "6.3 -1.5 9.0": ["framesets"], "3.4 7.6 5.5": ["stuggles"], "9.5 25.8 14.4": ["shabab"], "9.8 22.4 2.6": ["ilks"], "3.8 4.0 24.6": ["warung"], "-10.2 10.1 14.5": ["overclockability"], "7.8 -2.1 2.5": ["magalog"], "-5.0 8.9 0.7": ["traing"], "9.5 -2.4 10.3": ["aboout"], "12.7 18.3 7.4": ["facepalm"], "16.1 15.1 9.9": ["grap"], "3.8 2.1 13.0": ["curlier"], "5.5 3.0 6.3": ["tweenies"], "17.3 4.0 13.0": ["tousling"], "0.6 -0.1 7.5": ["wysiwyg"], "0.3 5.9 9.3": ["rearended"], "1.7 2.9 12.4": ["acetal"], "0.7 -3.0 -0.8": ["pleasevisit"], "-2.0 11.3 13.0": ["suscribe"], "-2.9 -5.7 20.8": ["restocker"], "21.3 1.9 12.9": ["pavillions"], "3.0 9.4 12.6": ["proximally"], "4.2 25.6 4.5": ["manouvres"], "14.3 23.5 3.9": ["transfigure"], "1.5 12.2 3.2": ["extenuation"], "3.6 12.0 6.8": ["photocurrent"], "7.2 10.1 5.7": ["vr"], "5.3 12.9 13.6": ["phylogenies"], "8.6 11.9 12.2": ["xlsx"], "2.5 5.0 9.3": ["nse"], "7.3 -1.3 9.3": ["fillips"], "11.8 13.5 8.8": ["ulta"], "16.6 20.0 3.1": ["giantkiller"], "11.0 5.1 10.6": ["harelip"], "6.1 12.9 11.6": ["motocrossers"], "19.8 16.8 9.7": ["skinflints"], "8.1 2.8 13.0": ["liscense"], "14.8 18.8 20.6": ["dodgeballs"], "17.6 4.7 23.5": ["wainscotting"], "-4.6 4.3 10.2": ["myocardin"], "2.7 24.8 13.1": ["subconsciousness"], "3.9 -9.2 -2.2": ["compl"], "1.8 13.0 14.5": ["carouser"], "-3.8 30.2 5.0": ["knower"], "7.4 7.0 7.2": ["myofascial"], "9.1 7.0 9.0": ["ofpeople"], "7.8 15.0 6.7": ["trypanosomes"], "14.9 7.0 6.0": ["pipelayers"], "1.2 3.9 5.7": ["atherogenesis"], "15.7 9.1 38.2": ["oilskins"], "5.3 4.5 17.2": ["chylomicrons"], "5.7 27.4 5.1": ["malignity"], "6.5 3.1 10.4": ["pues"], "12.3 19.1 10.5": ["dickish"], "4.3 3.7 6.4": ["backable"], "1.8 4.0 7.8": ["neotraditional"], "-1.5 3.9 4.8": ["eurovision"], "4.5 14.6 7.9": ["prodigality"], "7.5 5.6 10.3": ["cmos"], "3.9 -0.5 11.4": ["intravaginal"], "6.2 19.0 7.5": ["perfectible"], "10.0 10.8 8.0": ["branes"], "15.6 4.3 7.2": ["spreadbetting"], "7.8 10.9 8.0": ["tetchiness"], "9.6 13.3 11.2": ["flightpaths"], "16.7 -4.2 3.7": ["equivilant"], "3.3 8.0 18.5": ["sulphidic"], "14.3 15.2 11.0": ["sneery"], "4.7 7.9 6.7": ["inseams"], "10.4 6.8 14.7": ["athlon"], "9.2 15.4 18.5": ["salinisation"], "-9.4 6.5 1.4": ["comptrollership"], "-7.1 1.2 3.0": ["solifenacin"], "8.2 19.1 8.4": ["fervidly"], "1.6 12.0 16.2": ["undersexed", "nawawala"], "6.2 20.2 4.2": ["extrasensory"], "10.3 5.3 -3.9": ["telemedia"], "19.5 16.0 0.5": ["outdate"], "10.7 14.2 7.0": ["nanofactories"], "1.1 3.7 8.8": ["gastrocnemius"], "-2.2 12.8 0.4": ["deat"], "7.1 22.9 9.8": ["uncreated"], "0.9 9.1 14.0": ["tibias"], "-5.2 6.7 8.8": ["unbuffered"], "-2.9 5.9 2.0": ["pradesh"], "3.1 8.1 2.6": ["livest"], "7.5 -0.4 7.1": ["moda"], "2.4 3.3 4.4": ["nanotoxicology"], "6.6 1.2 8.5": ["catteries"], "2.4 7.7 7.9": ["celebrex"], "9.3 9.2 42.1": ["pimientos"], "13.7 9.0 29.3": ["irukandji"], "8.1 20.2 7.0": ["mightiness"], "20.5 11.3 33.7": ["rootbeer"], "-3.0 12.0 3.9": ["pathologizing"], "-2.3 1.6 0.4": ["isobutylene"], "-3.6 2.2 6.6": ["prehearing"], "3.1 11.0 19.2": ["electrum"], "4.5 7.0 21.2": ["taw"], "6.0 4.0 -4.9": ["sarl"], "5.0 0.6 0.7": ["qeep"], "7.5 13.1 8.5": ["pontificator"], "20.8 25.5 18.4": ["hellhound"], "1.2 0.3 4.3": ["multiparameter"], "15.9 12.9 21.7": ["mawashi"], "1.6 2.6 8.4": ["vinblastine"], "10.4 17.1 15.0": ["ehhh"], "15.6 19.2 10.4": ["vaporising"], "15.0 9.7 7.0": ["zou"], "14.9 9.8 3.9": ["sweatily"], "14.6 6.3 1.7": ["fullfledged"], "9.4 6.0 9.1": ["httpd"], "-9.1 3.8 2.3": ["foilist"], "3.1 5.4 14.5": ["blastomere"], "7.9 13.7 12.5": ["airsick"], "8.1 8.1 2.6": ["chelating"], "-3.5 38.8 7.7": ["agressor"], "13.0 -2.4 16.5": ["trifold"], "-1.7 -2.5 16.4": ["dina"], "12.0 20.7 -0.2": ["spyplane"], "6.1 8.4 10.7": ["symtoms"], "7.7 -0.4 2.1": ["bestof"], "-8.2 -4.4 5.5": ["periodontology"], "6.6 13.9 19.4": ["rua"], "-3.0 -12.2 0.8": ["sche"], "10.8 6.6 22.7": ["kalash"], "-3.8 5.7 -1.2": ["opinioned"], "7.2 -9.3 7.8": ["cfa"], "3.6 10.9 6.2": ["essien"], "18.1 6.7 17.6": ["wiff"], "5.6 18.7 5.0": ["consiglieri"], "1.0 -1.0 4.4": ["televote"], "5.3 20.5 27.0": ["aegypti"], "13.4 4.4 9.4": ["sardined"], "-3.9 -4.7 4.5": ["jur"], "-0.7 -2.4 5.7": ["antitussives"], "9.5 3.9 8.4": ["nanocoatings"], "2.9 3.4 14.7": ["prefrosh"], "8.2 3.6 7.5": ["rotomolding"], "2.9 15.2 13.8": ["meterologists"], "6.9 1.0 23.0": ["sawnwood"], "-4.9 18.4 0.3": ["proselytisation"], "1.3 9.1 10.7": ["clientelle"], "-0.8 2.6 13.0": ["nups"], "15.9 18.7 12.7": ["birdiefest"], "16.2 18.7 24.8": ["mmmmmm"], "5.1 4.3 3.5": ["nutricosmetics"], "5.3 9.8 11.4": ["headscarfs"], "9.6 23.3 7.8": ["immured"], "7.9 8.0 8.8": ["superannuants"], "5.1 6.3 19.8": ["brighteners"], "0.2 3.0 11.3": ["tariffed"], "10.8 11.2 19.5": ["trou"], "8.4 1.9 5.6": ["acrylates"], "3.7 3.6 10.5": ["galing"], "0.6 12.8 7.2": ["improtant"], "-1.3 15.0 3.4": ["unnacceptable"], "9.4 7.3 7.5": ["bewitchingly"], "4.3 7.1 15.0": ["xin"], "-1.6 10.6 10.7": ["hyperactivation"], "15.7 10.9 13.8": ["junkman"], "10.1 -4.9 17.3": ["nutri"], "6.2 1.9 -1.4": ["trackman"], "7.7 6.6 -4.2": ["betbull"], "22.1 1.3 36.8": ["chourico"], "3.7 5.4 10.6": ["innoculations"], "4.4 3.9 6.0": ["skybus"], "6.0 19.6 8.6": ["tritely"], "-2.5 16.8 -1.4": ["panchas"], "7.5 0.9 4.2": ["reclosers"], "20.0 15.5 5.5": ["exaflop"], "-8.9 30.2 2.5": ["kandak"], "11.6 2.3 16.0": ["vela"], "21.0 17.4 17.8": ["hieroglyph"], "-6.3 2.6 -5.6": ["mammographer"], "13.7 14.9 14.0": ["hiccoughs"], "1.1 12.1 5.8": ["summiteer"], "12.0 15.6 6.3": ["klavern"], "8.3 9.6 17.3": ["thriftily"], "-2.7 8.3 13.8": ["globin"], "7.9 17.7 9.2": ["hinduism"], "7.8 8.6 7.6": ["prisonlike"], "16.6 4.1 5.8": ["pantyless"], "4.1 12.4 7.1": ["interupt"], "-1.7 6.9 14.6": ["runscoring"], "1.8 10.6 8.4": ["abba"], "10.1 3.3 8.6": ["alk"], "5.4 7.8 -5.0": ["ergonomists"], "8.7 2.2 3.1": ["bioenergetics"], "19.1 9.1 -0.1": ["lables"], "4.6 -1.4 4.9": ["shotputter"], "1.8 4.6 -0.9": ["operatories"], "-0.8 7.7 10.3": ["cardiolipin"], "9.0 22.9 9.6": ["flechettes"], "-10.1 10.4 8.8": ["errored"], "4.1 3.4 8.1": ["pyrophosphate"], "0.9 12.2 18.8": ["repletion"], "4.7 6.0 12.1": ["paten"], "30.9 10.0 23.4": ["diplodocus"], "11.0 16.4 26.0": ["shedders"], "4.6 21.4 25.0": ["medfly"], "1.8 6.2 15.5": ["leachates"], "5.3 -9.4 12.6": ["hampton"], "11.4 23.1 20.4": ["pestilences"], "6.1 14.2 12.3": ["weres"], "-0.7 7.1 7.1": ["linalool"], "6.8 39.1 4.7": ["mullahcracy"], "2.3 -7.8 2.5": ["offerd"], "0.8 6.8 12.6": ["stepgranddaughter"], "14.1 13.2 16.3": ["raddest"], "3.9 0.3 6.5": ["colum"], "6.9 9.7 21.2": ["stemless"], "9.1 15.6 5.9": ["evryone"], "0.8 0.8 11.8": ["enfants"], "3.5 22.7 -0.5": ["cryptologic"], "11.4 17.0 33.8": ["australis"], "9.2 8.6 6.0": ["intercooling"], "5.9 9.4 22.1": ["divemaster"], "10.4 15.5 2.5": ["arclights"], "2.7 13.2 1.2": ["buzzd"], "4.0 9.2 29.9": ["grillin"], "-6.1 3.9 -3.3": ["esd"], "-4.7 -0.7 -2.1": ["ement"], "17.2 5.6 10.2": ["concertinaed"], "5.7 8.1 11.3": ["yorking"], "-4.1 2.5 8.3": ["churchwardens"], "2.4 -0.3 -0.2": ["workstream"], "7.5 13.6 14.1": ["makutu"], "12.8 -8.4 -1.8": ["longawaited"], "-1.3 11.6 9.8": ["stoichiometry"], "8.3 14.6 8.5": ["refree"], "-6.1 4.4 2.1": ["cbse"], "5.5 25.6 1.8": ["mendaciously"], "14.1 16.3 16.7": ["supernal"], "15.4 5.9 10.6": ["clattery"], "21.9 8.3 -1.9": ["programers"], "-4.1 2.2 19.0": ["calvers"], "1.8 14.5 4.7": ["counteractive"], "17.3 9.1 11.0": ["horseshoed"], "3.2 19.2 4.1": ["tumultuously"], "17.9 -1.4 13.3": ["ormolu"], "-4.6 3.1 -2.1": ["retouches"], "6.3 10.9 5.3": ["crt"], "1.3 15.8 7.0": ["prostrations"], "14.2 12.0 12.4": ["dells"], "7.3 1.1 13.6": ["soubrette"], "2.8 0.2 4.7": ["museology"], "2.4 20.4 7.8": ["buddhists"], "-2.1 18.9 5.4": ["atma"], "10.0 0.9 8.9": ["lakeland"], "-0.5 12.7 10.9": ["oftener"], "3.9 7.9 17.2": ["amylopectin"], "17.9 15.9 2.9": ["fetishised"], "14.3 -1.2 7.4": ["ironmongers"], "3.4 4.5 14.1": ["zac"], "2.0 8.8 13.7": ["cuppers"], "13.2 15.1 -4.7": ["wihout"], "11.0 5.5 14.7": ["scintilating"], "7.6 -6.1 8.9": ["clubwear"], "8.4 10.2 11.6": ["spose"], "17.2 9.5 14.2": ["woop"], "8.9 7.1 11.2": ["shlepping"], "3.3 15.5 7.5": ["surprize"], "7.2 24.2 8.0": ["invastion"], "8.3 -2.4 7.1": ["webite"], "5.5 5.1 7.1": ["aftr"], "-0.0 4.3 9.3": ["oklahoman"], "7.7 4.6 2.8": ["reciept"], "16.3 15.8 14.7": ["suppurating"], "14.7 5.9 9.9": ["photoreal"], "1.9 -5.0 19.0": ["opa"], "14.5 2.2 11.5": ["tramcar"], "0.4 14.0 8.3": ["unthoughtful"], "-3.3 10.3 7.8": ["churchly"], "17.0 12.9 26.1": ["dapples"], "5.0 8.3 15.1": ["unremunerative"], "11.4 3.2 5.6": ["vantages"], "0.2 4.5 3.8": ["prescripts"], "3.4 3.8 10.6": ["reflexologists"], "3.5 12.3 2.8": ["effor"], "7.8 5.9 42.8": ["flattie"], "7.7 4.0 18.0": ["bedder"], "17.7 25.4 16.6": ["untameable"], "2.7 6.0 16.6": ["dese"], "4.2 -6.4 -0.8": ["contrac"], "11.2 1.1 14.3": ["tartrazine"], "16.1 4.0 9.6": ["whenas"], "11.2 18.8 4.7": ["unexampled"], "10.3 22.7 15.5": ["splog"], "-3.6 6.6 3.9": ["ponente"], "7.2 10.1 19.9": ["heathlands"], "-0.9 2.0 -0.6": ["monoamine"], "-0.5 1.5 12.2": ["danse"], "19.0 16.2 17.9": ["saturn"], "-0.5 13.7 10.8": ["horseplaying"], "7.0 15.4 8.7": ["behaviorism"], "6.2 32.1 12.8": ["attackable"], "11.5 4.3 14.1": ["equitized"], "19.2 26.5 12.5": ["despoilers"], "24.8 4.4 12.0": ["intoa"], "-0.2 -2.7 4.7": ["suring"], "7.3 3.6 8.3": ["housesit"], "5.7 23.4 6.6": ["thepeople"], "-5.8 3.7 13.5": ["culturals"], "6.5 22.0 1.2": ["presnap"], "-2.8 8.3 3.9": ["reaffirmations"], "0.5 1.4 8.9": ["domperidone"], "1.0 -3.4 7.4": ["telebriefing"], "4.6 6.6 16.7": ["dunn"], "7.6 -1.0 9.9": ["ews"], "7.6 3.5 10.0": ["mullion"], "19.6 9.2 25.9": ["gunnysack"], "7.7 6.4 14.1": ["allan"], "3.8 5.4 9.1": ["zovirax"], "-18.3 1.8 3.4": ["rew"], "-1.1 5.3 5.8": ["baar"], "1.9 5.5 11.8": ["recompression"], "16.8 -3.5 4.0": ["ophthalmics"], "-2.1 5.5 8.5": ["endometritis"], "10.7 4.1 16.3": ["pantsing"], "4.9 7.6 20.0": ["thermophilic"], "-2.0 -5.8 6.0": ["debarments"], "7.4 17.7 13.4": ["backchecked"], "3.6 26.9 2.6": ["counteractions"], "25.0 18.0 10.8": ["clanky"], "4.1 10.3 5.2": ["presell"], "-2.8 11.9 7.7": ["infelicities"], "6.5 10.4 14.3": ["intradivisional"], "11.2 2.8 9.3": ["rewrapping"], "8.9 10.9 6.9": ["inode"], "7.3 13.5 9.1": ["payloaders"], "2.4 -2.0 10.0": ["nding"], "5.5 5.6 8.5": ["carbondioxide"], "12.9 3.0 6.1": ["robbin"], "9.9 10.9 11.6": ["infinitum"], "13.6 7.9 16.5": ["ufo"], "6.7 15.1 16.1": ["assonance"], "-19.3 -3.2 3.9": ["shiurim"], "24.9 23.2 9.4": ["cataclysmically"], "7.7 10.9 15.6": ["homesellers"], "11.6 25.3 1.3": ["bulletproofed"], "23.6 2.5 2.5": ["cheergirls"], "-6.9 8.1 3.7": ["prevision"], "18.2 15.2 23.8": ["burls"], "13.6 13.1 36.8": ["banchan"], "22.8 14.0 7.5": ["enshrouding"], "17.5 14.1 7.3": ["plankers"], "11.5 8.3 9.5": ["recessionistas"], "7.2 10.2 14.3": ["uf"], "2.1 12.1 6.3": ["extensor"], "13.1 15.9 11.9": ["reflagging"], "10.5 2.7 13.6": ["punchcard"], "7.1 9.6 11.8": ["acca"], "3.1 7.0 8.6": ["plateward"], "-7.4 2.4 7.4": ["hypotonia"], "12.8 17.0 15.6": ["dreamgirl"], "-8.2 26.4 -0.1": ["tendentiously"], "-7.7 20.9 9.4": ["nondeployed"], "5.9 21.7 32.1": ["lovebug"], "9.3 12.9 22.1": ["receipe"], "6.7 16.1 9.0": ["inelegance"], "20.0 19.6 14.0": ["swingometer"], "14.2 8.4 4.6": ["inclinometers"], "18.5 -2.7 5.6": ["servi"], "-11.1 4.6 4.3": ["reconvicted"], "13.0 11.6 5.1": ["headon"], "-4.2 4.9 14.3": ["carnosine"], "5.4 11.4 2.1": ["inerting"], "-2.7 4.7 4.5": ["educ"], "-4.7 12.1 12.0": ["itna"], "1.2 10.0 -7.0": ["knowlegde"], "0.8 2.6 8.3": ["minimarkets"], "10.8 9.3 7.2": ["acerno"], "9.9 7.1 13.8": ["deodar"], "0.2 10.7 4.9": ["hcap", "chachi"], "-1.2 -2.2 11.4": ["cft"], "8.8 7.6 8.0": ["fireballers"], "6.1 4.3 1.6": ["contiue"], "-0.7 23.7 5.0": ["unreligious"], "9.8 10.7 23.1": ["chola"], "3.3 2.2 1.3": ["sameperiod"], "12.1 -3.4 6.8": ["tipo"], "2.9 8.8 22.6": ["kneeboarding"], "3.1 4.4 1.6": ["anonymizes"], "8.9 6.1 20.7": ["cubano"], "4.4 15.2 10.5": ["ciphertext"], "-1.0 13.0 8.8": ["keratosis"], "7.0 -3.4 10.0": ["fundrasing"], "5.1 -3.4 25.3": ["crme"], "3.3 6.0 0.9": ["linkedin"], "-1.8 5.3 11.8": ["agriturismo"], "-1.4 15.8 4.6": ["incestuously"], "-7.8 1.4 -2.0": ["nonconfidential"], "3.2 -4.1 -0.4": ["preheater"], "6.7 14.8 23.7": ["lightkeepers"], "8.2 0.9 10.1": ["quai"], "-4.1 4.5 11.3": ["bandish"], "7.6 4.4 16.5": ["showbizzy"], "5.7 2.6 8.2": ["pelo"], "1.7 1.5 12.5": ["hirees"], "6.3 14.3 0.0": ["goalminder"], "-2.3 11.1 13.0": ["allogenic"], "2.3 4.0 8.5": ["fosterers"], "0.1 10.4 9.5": ["haplogroups", "leptospira"], "9.9 -1.4 9.9": ["unemptied"], "6.2 25.4 8.5": ["ignobly"], "6.3 10.7 11.8": ["amirite"], "4.7 24.3 12.6": ["antipodal"], "6.5 10.8 17.9": ["demanders"], "3.5 8.9 9.0": ["doorbelling"], "9.9 -1.2 -2.2": ["brandnew"], "-4.4 1.8 22.3": ["earlies"], "-0.4 7.1 12.0": ["meterage"], "3.8 26.7 14.1": ["haggler"], "8.3 4.3 3.8": ["tokidoki"], "-0.6 29.6 9.4": ["woundedness"], "4.1 11.3 10.2": ["gruffer"], "11.3 5.7 31.2": ["heliconia"], "0.1 2.6 3.7": ["dextofisopam"], "8.2 11.5 14.9": ["phoren"], "-2.2 15.6 1.2": ["satya"], "-4.5 17.1 1.1": ["personnally"], "7.9 4.4 -1.6": ["turbocharges"], "-0.1 7.6 3.0": ["outraises"], "11.8 9.9 15.5": ["ladys"], "1.5 18.1 3.8": ["ingroup"], "5.2 20.4 8.0": ["stoics"], "23.8 10.1 20.0": ["winglike"], "8.9 10.2 9.9": ["sanguinity"], "7.2 21.6 9.7": ["hmmmmmm"], "3.9 19.1 8.1": ["malays"], "-0.3 4.3 0.1": ["propeled"], "-1.4 14.6 3.8": ["diffrence"], "7.8 8.7 6.2": ["chale"], "2.8 19.5 0.7": ["interpol"], "-2.7 10.7 -7.8": ["campaiging"], "8.2 3.7 9.1": ["cholecystokinin"], "9.8 15.9 4.4": ["forebode"], "8.7 -3.9 7.1": ["trimestre"], "14.4 6.3 5.7": ["pire"], "-0.5 3.4 -0.8": ["noninstitutional"], "-2.4 4.9 -2.9": ["adminstered"], "0.7 11.6 12.6": ["uld"], "10.3 2.2 12.7": ["waterblock"], "15.8 17.6 18.4": ["laddies"], "2.5 4.8 5.3": ["glycosaminoglycans"], "-2.2 1.4 15.9": ["mukhang"], "13.0 14.0 9.5": ["barack"], "19.6 22.4 12.7": ["infared"], "0.9 6.0 5.8": ["paracetemol"], "12.0 20.2 7.6": ["abase"], "11.5 12.6 27.2": ["plenteous"], "7.9 22.2 11.7": ["sombody"], "-2.9 1.2 6.2": ["houseparents"], "6.4 10.9 -3.2": ["deliever"], "8.9 8.5 20.2": ["kavadi"], "5.1 14.5 9.9": ["humoristic"], "4.2 7.8 17.2": ["laffs"], "21.0 17.0 24.7": ["spume"], "18.0 -4.6 14.7": ["reclosable"], "6.6 6.6 20.9": ["malo"], "-1.0 1.6 2.2": ["ackowledged"], "13.5 5.3 14.2": ["barrelhouse"], "-0.2 -3.4 14.1": ["taon"], "10.0 16.2 16.8": ["sighters"], "15.7 9.2 16.1": ["vainest"], "18.1 13.7 37.7": ["sammich"], "20.4 6.0 11.8": ["nanolasers"], "4.3 19.8 2.7": ["kiled"], "3.6 7.6 12.6": ["planarity"], "11.3 3.7 6.6": ["prenegotiated"], "11.7 17.4 15.2": ["supervolcanoes"], "7.2 7.5 20.9": ["tadka"], "24.3 5.8 19.3": ["stiltwalkers"], "6.7 5.4 14.8": ["fiel"], "13.5 21.1 -0.6": ["forbearer"], "-3.8 8.7 6.1": ["dhrupad"], "2.2 8.6 8.5": ["orthophotos"], "-0.9 4.8 10.5": ["schoolish"], "11.2 7.4 8.2": ["nanosheets"], "16.3 3.3 11.1": ["centimos"], "4.8 15.5 22.4": ["amala"], "1.7 18.7 5.3": ["posteriori"], "-1.6 10.7 4.2": ["diesem"], "-1.8 0.9 1.0": ["whp"], "3.2 22.7 0.5": ["semblence"], "9.4 16.6 7.6": ["gamepage"], "12.9 10.6 16.7": ["hankerings"], "1.4 6.5 16.9": ["cosa"], "-0.3 5.5 5.6": ["zolmitriptan"], "8.7 20.0 6.9": ["indistinctly"], "20.8 7.8 14.9": ["meshwork"], "18.3 5.5 3.9": ["swaddles"], "-2.9 0.2 3.7": ["rao"], "10.6 7.7 19.6": ["mahua"], "10.3 16.1 2.0": ["hims"], "6.0 13.9 1.9": ["qode"], "3.3 0.9 7.9": ["cobalamin"], "11.6 8.8 17.9": ["habs"], "4.3 26.6 10.2": ["rageful"], "8.1 2.7 3.9": ["vulcanization"], "10.5 17.1 12.1": ["deads"], "20.0 18.4 27.1": ["tastebud"], "-7.2 15.9 11.8": ["witout"], "3.4 -10.9 2.2": ["rehabilition"], "4.0 -5.7 -1.0": ["manag"], "-0.8 -0.2 1.8": ["underbilling"], "0.9 19.6 5.0": ["sentimentalizing"], "5.6 12.0 17.3": ["radix"], "9.1 24.8 14.9": ["bubonic"], "17.8 8.7 17.2": ["favre"], "10.2 8.8 14.9": ["lers"], "11.2 10.4 1.9": ["eternalized"], "-4.1 22.5 2.7": ["quietism"], "8.5 8.5 -1.6": ["tems"], "10.6 14.6 22.9": ["gringa"], "13.3 17.9 9.1": ["linksys"], "2.5 0.0 0.0": ["ller", "solidaire"], "3.5 19.0 2.5": ["syndicalists"], "13.6 -0.2 10.9": ["juni"], "-2.7 1.3 15.9": ["youngstock"], "11.5 7.8 16.7": ["expeller"], "0.3 1.8 6.3": ["cytopathology"], "4.2 3.3 6.8": ["cdc"], "9.9 6.4 9.2": ["privitization"], "1.2 17.2 4.5": ["improvable"], "13.3 4.4 13.2": ["cist"], "17.5 9.9 9.9": ["nowheresville"], "5.3 16.2 4.7": ["machoism"], "18.7 -3.1 5.2": ["quaterly"], "-3.0 -3.6 5.3": ["abstractors"], "9.7 15.3 12.1": ["deconstructionists"], "-2.5 13.0 13.2": ["kasalanan"], "-3.9 9.0 7.3": ["cyclophilin"], "9.1 18.6 10.7": ["factotums"], "5.8 3.9 16.1": ["inground"], "11.7 3.1 2.9": ["bancassurers"], "6.8 1.9 7.8": ["courtesty"], "0.7 17.4 -1.4": ["tabooed"], "7.2 10.5 12.9": ["dani"], "-5.8 9.6 -4.1": ["youl"], "3.4 8.0 12.3": ["midcalf"], "2.0 22.6 0.8": ["sacredly"], "-3.8 2.6 9.5": ["unrecruited"], "-0.1 2.6 -5.2": ["withinthe"], "5.0 6.7 -5.0": ["couriering"], "5.6 27.3 12.4": ["roguery"], "9.9 18.3 31.7": ["budworm"], "12.4 6.8 3.0": ["reconceive"], "4.8 12.3 11.8": ["chelski"], "-7.7 5.0 0.4": ["disctrict"], "10.8 3.5 11.0": ["msi"], "-1.2 8.7 8.2": ["libretti"], "0.8 10.8 8.5": ["practicably"], "4.1 12.6 4.7": ["ullage"], "4.4 8.3 3.8": ["glucocerebrosidase"], "0.7 11.9 11.9": ["maked"], "10.4 1.4 15.7": ["astrakhan"], "8.0 7.5 11.2": ["depolarisation"], "-7.1 13.8 7.5": ["circumcisers"], "8.2 10.5 6.5": ["spermicides"], "15.7 10.7 17.4": ["agitatedly"], "1.1 15.1 3.9": ["bette"], "12.8 26.2 18.1": ["corsair"], "8.8 8.5 11.9": ["searchingly"], "14.8 19.6 20.1": ["pankration"], "-1.6 3.5 15.3": ["autografts"], "-4.0 9.3 11.3": ["differentiable"], "-3.0 7.5 0.6": ["kisanja"], "12.9 16.3 18.5": ["splashback"], "18.0 12.6 15.5": ["castlelike"], "-0.1 13.4 13.1": ["burglarly"], "-1.0 -0.6 6.1": ["tsy"], "-0.6 12.7 16.4": ["hazer"], "5.8 14.6 7.9": ["toilsome"], "1.6 9.8 10.7": ["lubricin"], "6.7 18.2 1.3": ["hateable"], "8.6 21.5 17.3": ["culturist"], "20.3 18.6 6.0": ["wolrd"], "11.3 18.5 -5.4": ["immolating"], "19.9 18.4 21.9": ["earless"], "5.7 11.1 14.9": ["overbookings"], "7.9 7.8 27.8": ["inflorescences"], "3.8 3.2 18.1": ["handspun"], "0.3 -3.8 23.3": ["woodturner"], "3.5 -0.7 14.3": ["primera"], "-1.3 10.0 6.1": ["organogenesis"], "13.5 8.1 0.6": ["tecnology"], "15.9 11.5 24.4": ["turtledoves"], "-3.4 8.4 2.9": ["ensoulment"], "4.8 17.0 0.3": ["videocams"], "-0.4 8.2 5.3": ["neuroinvasive"], "7.2 27.0 11.8": ["unappeasable"], "9.6 14.2 17.2": ["grandpop"], "17.9 11.9 18.1": ["bounciest"], "18.6 7.7 19.1": ["camello"], "19.2 -2.2 3.5": ["printworks"], "7.1 8.9 47.3": ["surfperch"], "4.6 11.0 8.1": ["magnetometry"], "12.4 24.3 17.4": ["minisub"], "24.5 14.9 11.9": ["chainsawed"], "2.4 6.8 4.6": ["uest"], "3.4 1.6 16.4": ["grandmoms"], "9.4 9.7 9.2": ["tibet"], "24.0 5.7 30.7": ["butty"], "1.4 17.2 6.0": ["agitationists"], "7.2 6.3 23.7": ["chaats"], "0.6 9.5 4.4": ["staus"], "15.6 21.6 6.1": ["conspicuousness"], "3.1 6.7 11.5": ["itz"], "13.6 19.0 12.5": ["infernally"], "17.0 3.0 11.5": ["removalist"], "-0.8 1.4 8.4": ["devo"], "6.1 25.3 1.4": ["reconnoitered"], "12.5 17.6 15.2": ["shivs"], "-7.5 2.8 8.0": ["refactorings"], "14.2 14.8 34.7": ["maru"], "14.1 -1.6 -2.4": ["contraversial"], "8.9 0.5 14.2": ["seta"], "5.6 5.6 18.1": ["attar"], "8.7 4.4 15.5": ["hele"], "5.1 18.7 3.5": ["overcommitment"], "13.3 3.3 12.9": ["tyred"], "-1.4 4.3 33.1": ["stillwaters"], "10.3 4.2 15.1": ["viene"], "21.6 19.6 20.5": ["frakkin"], "2.4 10.6 12.9": ["cohen"], "-1.4 19.0 7.7": ["enculturation"], "0.0 17.7 6.7": ["consigliore"], "9.4 14.1 31.0": ["spicebush"], "-1.1 4.2 10.2": ["holoprosencephaly"], "12.2 15.9 7.8": ["fullstop"], "8.7 -2.1 -0.4": ["carveout"], "3.0 3.5 9.1": ["khabar"], "-1.2 -4.9 4.3": ["baccalaureates"], "7.5 0.9 22.6": ["basketmaking"], "18.7 11.5 21.0": ["brussels"], "9.8 21.9 8.0": ["westernize"], "-1.3 -2.0 0.7": ["ives"], "5.9 5.1 4.9": ["databasing"], "0.5 16.6 10.8": ["underappreciation"], "9.2 -1.0 13.2": ["ecotoxicology"], "11.8 9.4 34.9": ["razorbills"], "6.9 17.7 7.9": ["nongraphic"], "-0.1 7.0 9.5": ["precompiled"], "19.2 3.0 17.7": ["quiffed"], "-0.6 5.7 -0.9": ["ahigh"], "9.9 11.6 7.8": ["handywork"], "-3.9 10.1 11.1": ["yaad"], "0.6 -6.7 10.9": ["jeunesse"], "1.5 0.9 14.8": ["unhoused"], "1.5 9.8 1.1": ["ecumenist"], "5.6 11.6 7.1": ["nonmainstream"], "13.2 23.1 17.0": ["maelstroms"], "10.7 10.3 -1.3": ["rescale"], "-1.2 -0.9 8.3": ["bagan"], "7.3 -2.1 1.7": ["whilethe"], "-1.9 4.7 21.0": ["apigenin"], "10.0 3.4 8.6": ["linotype"], "13.1 13.0 8.8": ["wholescale"], "4.4 13.9 8.1": ["seamheads"], "-1.5 23.1 10.1": ["purposively"], "2.9 0.7 14.8": ["tahn"], "-6.5 2.4 9.6": ["grayshirts"], "8.5 9.0 22.8": ["beachbreak"], "3.6 15.2 7.7": ["dentally"], "0.6 4.6 5.4": ["recontracting"], "3.8 5.1 11.7": ["telemarkers"], "13.8 16.6 18.8": ["pigsties"], "5.9 11.5 8.1": ["procompetitive"], "0.4 11.6 7.9": ["nonfrivolous"], "16.5 15.1 12.7": ["nannyism"], "13.0 15.7 16.0": ["hunchbacks"], "0.4 11.8 3.3": ["believ"], "5.0 -6.1 -5.5": ["ncluding"], "4.9 13.4 14.4": ["disjunct"], "14.6 10.8 13.8": ["ducal"], "3.7 7.5 7.5": ["clubsite"], "8.0 3.0 8.6": ["rollstock"], "-5.5 7.9 1.9": ["adduces"], "-4.6 1.3 6.5": ["upazilla"], "5.6 14.2 11.8": ["unmuffled"], "9.0 16.8 25.0": ["lifeboatman"], "-0.4 4.3 25.0": ["huli"], "17.1 13.1 9.2": ["pipebomb"], "10.4 20.4 17.8": ["simp"], "5.1 0.0 11.4": ["tana"], "12.0 13.8 15.3": ["wabs"], "3.0 15.8 9.5": ["trishuls"], "9.2 -1.9 16.9": ["koe"], "2.3 13.5 10.7": ["synesthetic"], "23.6 1.9 11.7": ["eyewatering"], "7.8 18.4 4.0": ["rigth"], "2.4 9.3 14.6": ["playboat"], "1.7 5.5 3.9": ["fixator"], "-1.2 6.5 4.7": ["subparagraphs"], "9.3 13.4 11.2": ["myofibroblasts"], "1.8 13.0 5.9": ["mahatma"], "2.4 19.5 10.9": ["syllogisms"], "8.1 12.6 12.5": ["doppelbock"], "12.5 11.2 35.7": ["ortolan"], "2.4 17.4 16.2": ["outswinging"], "19.2 -3.2 -2.5": ["acq"], "12.5 16.2 12.8": ["airness"], "0.3 16.6 2.8": ["opinionating"], "-6.2 6.1 4.2": ["adducts"], "12.9 6.0 35.4": ["poulet"], "4.8 4.2 15.6": ["phenotypically"], "14.9 3.1 18.4": ["nonbiodegradable"], "5.9 7.2 22.9": ["gola"], "2.8 10.6 8.2": ["radiuses"], "20.4 14.0 17.6": ["whackers"], "7.1 16.3 11.4": ["uck"], "3.5 0.4 5.7": ["neratinib"], "7.1 5.9 12.9": ["paleoclimatology"], "-4.1 0.5 11.9": ["dysgeusia"], "2.7 2.1 12.6": ["osseointegration"], "-4.5 10.7 15.4": ["menin"], "15.4 8.1 21.5": ["staler"], "12.9 -10.3 3.8": ["sponsorhip"], "-0.1 4.0 3.9": ["ersten"], "11.7 1.8 5.1": ["thethree"], "-4.9 3.8 13.7": ["niraval"], "5.2 7.7 -1.3": ["walkmans"], "8.0 15.1 21.5": ["copulated"], "7.8 21.9 16.8": ["ghaf"], "5.6 12.4 14.6": ["minimumweight"], "2.0 9.5 0.3": ["mandirs"], "12.1 1.6 0.9": ["microvan"], "-4.6 15.5 4.5": ["ascription"], "2.8 -4.8 18.5": ["gamba"], "14.1 5.5 19.6": ["quilling"], "6.5 7.7 6.1": ["infeasibility"], "-5.9 5.6 0.4": ["quantative"], "17.2 4.5 10.8": ["swith"], "19.5 4.9 10.7": ["bubblicious"], "9.4 2.5 5.7": ["foir"], "3.5 20.7 0.4": ["premeditating"], "-0.5 -3.2 10.7": ["octets"], "3.8 7.9 4.2": ["diesen"], "0.1 9.0 3.4": ["deflators"], "16.5 3.2 4.4": ["tollroads"], "4.8 41.1 -2.5": ["beheaders"], "17.2 3.2 -2.5": ["hypermodern"], "7.7 0.2 8.3": ["barbered"], "10.5 3.1 18.3": ["carnivale"], "4.9 7.5 13.0": ["vaction"], "16.1 8.3 15.9": ["suya"], "14.8 4.3 23.3": ["surfy"], "14.9 27.8 25.9": ["sandfly"], "2.4 11.6 23.8": ["cyanobacterial"], "2.1 9.8 1.8": ["institutionalises"], "5.6 0.5 5.2": ["tih"], "5.1 4.3 -5.6": ["demostrated"], "11.5 14.8 8.4": ["fellate"], "19.6 17.3 10.7": ["outflowing"], "-3.0 8.0 -2.3": ["inconnection"], "8.7 3.6 21.0": ["cowdung"], "19.0 27.1 19.3": ["reddens"], "11.0 24.8 11.6": ["antiparticle"], "2.2 7.8 27.7": ["sugarmakers"], "4.2 19.3 18.1": ["brutha"], "-3.4 8.2 9.6": ["remineralization"], "0.4 12.0 7.4": ["overweigh"], "14.0 23.3 18.8": ["iceball"], "-4.7 12.5 12.1": ["exaltations"], "0.6 9.8 18.5": ["maal"], "16.7 11.8 18.4": ["bizness"], "13.5 11.5 15.6": ["kookiest"], "-0.7 19.7 7.7": ["athiests"], "16.9 11.7 -0.1": ["phoneless"], "11.1 22.5 11.2": ["taunters"], "2.4 11.0 16.9": ["bua"], "9.5 10.5 6.6": ["fletcher"], "2.6 11.1 8.8": ["greynets"], "10.0 6.8 24.7": ["wolfberry"], "5.5 14.0 20.5": ["nikki"], "6.6 2.7 2.7": ["saccos"], "6.0 14.1 9.4": ["logarithmically"], "2.7 26.3 3.4": ["acurate"], "0.5 19.9 -4.0": ["achieveing"], "12.0 13.0 28.1": ["feijoa"], "7.9 6.3 21.0": ["stockbreeding"], "3.2 2.8 10.1": ["aquatints"], "13.0 -8.6 -4.6": ["isone"], "10.4 21.6 8.8": ["enchanter"], "10.0 13.1 19.7": ["honkies"], "7.4 15.8 24.6": ["brooders"], "14.0 16.4 5.2": ["backin"], "8.2 10.7 13.8": ["regex"], "6.2 14.1 6.1": ["demob"], "5.2 4.9 12.6": ["cyanotype"], "-5.1 1.3 12.0": ["longtimers"], "9.6 4.2 13.6": ["eish"], "2.1 17.9 6.6": ["bureaucratised"], "12.8 7.0 11.6": ["gama"], "13.6 0.5 11.6": ["sharebroker"], "7.4 3.6 14.0": ["nuptuals"], "10.4 8.6 21.3": ["doggin"], "10.5 6.3 8.2": ["econtent"], "12.6 5.9 11.7": ["palaeontological"], "6.8 10.0 9.3": ["spoofery"], "4.4 6.8 10.7": ["crix"], "19.2 19.7 24.6": ["supermaxis"], "18.2 9.0 4.7": ["distrubution"], "2.0 13.5 -1.7": ["relavent"], "6.1 3.1 27.9": ["dredgings"], "8.2 15.5 17.9": ["telos"], "0.3 8.3 20.5": ["lambics"], "15.8 23.1 13.7": ["sterotype"], "5.7 16.2 12.1": ["superciliousness"], "3.4 -0.3 18.5": ["rumah"], "10.2 14.4 16.6": ["romans"], "1.5 6.4 4.5": ["administrable"], "6.2 21.4 8.4": ["particularistic"], "15.1 18.8 16.7": ["droogs"], "-7.8 8.4 -2.9": ["nonwinner"], "16.1 -3.5 4.9": ["wigmaker"], "2.7 4.7 4.3": ["glibenclamide"], "13.9 29.1 16.2": ["laager"], "3.6 9.6 4.3": ["bitstreams"], "-4.4 -1.1 10.5": ["ited"], "17.3 18.7 15.7": ["waywardly"], "14.0 8.6 0.3": ["theinternational"], "0.8 17.3 10.0": ["postively"], "0.9 3.3 8.7": ["lintuzumab"], "-0.6 14.8 -13.3": ["whohas"], "9.4 6.6 1.3": ["despites"], "24.2 2.6 11.5": ["stodgiest"], "-5.4 3.1 1.1": ["ntv"], "11.1 10.6 3.2": ["apeared"], "10.1 11.1 18.9": ["countersunk"], "14.5 1.5 3.6": ["sanofi"], "5.8 2.5 8.8": ["grammys"], "-2.0 20.0 8.4": ["desiderata"], "8.7 25.0 13.4": ["downwash"], "10.7 21.4 5.1": ["geospatially"], "2.3 7.5 12.8": ["granitoids"], "0.4 4.9 5.2": ["polyamine"], "2.2 8.6 9.4": ["expunges"], "-10.5 10.1 -4.8": ["assit"], "-2.0 7.8 39.5": ["charterboat"], "1.7 6.4 9.8": ["nonregular"], "-3.8 12.7 4.7": ["bibi"], "7.7 3.6 11.3": ["glycomics"], "2.0 20.2 1.7": ["tenents"], "25.5 10.4 35.0": ["oreo"], "3.9 5.3 12.7": ["atin"], "8.1 6.2 -1.3": ["intergrate"], "8.8 -2.8 6.8": ["multicampus"], "-3.6 9.9 -2.5": ["wilaya"], "-1.6 14.7 8.5": ["freq"], "-0.8 -1.0 5.7": ["glycosaminoglycan"], "17.4 9.7 24.6": ["caravel"], "4.0 10.7 11.0": ["silicic"], "7.6 15.1 10.9": ["micky"], "10.5 6.2 11.7": ["handjobs"], "16.1 8.3 18.1": ["sups"], "8.0 9.5 -0.1": ["apears"], "10.1 19.4 16.4": ["weatherperson"], "13.2 13.8 7.1": ["bedouins"], "10.6 1.2 16.9": ["hoose"], "10.0 5.5 -1.9": ["deutsch"], "-6.3 0.0 -1.3": ["toour"], "4.4 -0.9 4.4": ["aca"], "11.3 15.1 9.0": ["fooking"], "0.1 15.5 7.0": ["preferrable"], "10.2 18.9 11.3": ["popinjay"], "13.0 12.9 4.7": ["manufactories"], "13.0 14.8 30.1": ["bowline"], "5.4 2.1 -3.7": ["effiency"], "9.5 20.2 4.3": ["unconducive"], "12.9 10.7 30.1": ["kafta"], "12.8 8.4 22.0": ["towrope"], "2.8 11.6 12.1": ["happ"], "4.0 16.7 5.8": ["privledge"], "-2.3 17.7 2.8": ["devistating"], "13.3 2.1 22.7": ["gabion"], "-1.2 -1.2 9.6": ["amis"], "16.3 5.0 11.4": ["matresses"], "4.0 16.1 15.4": ["horticulturally"], "4.9 11.6 -0.4": ["disinterring"], "7.2 4.3 14.9": ["loveably"], "20.7 1.5 5.0": ["fastgrowing"], "13.0 11.5 13.7": ["afl"], "12.4 13.3 9.9": ["inconsequentially"], "5.9 1.9 1.3": ["sigue"], "11.5 18.4 30.0": ["honeysuckles"], "-7.4 -1.3 -3.0": ["tolterodine"], "-0.0 7.7 0.8": ["housefull"], "2.5 27.6 4.1": ["tailgunner"], "10.8 12.8 17.6": ["lota"], "1.2 20.4 16.4": ["shotshells"], "10.3 8.0 18.0": ["transcriptomes"], "2.4 12.6 2.9": ["philologists"], "14.7 14.8 32.1": ["salps"], "10.7 -2.0 34.1": ["crucians"], "13.1 18.4 7.8": ["fabulists"], "7.6 1.2 11.9": ["ypv"], "-0.2 11.2 10.8": ["sorrys"], "-1.4 10.7 -3.8": ["touse"], "9.7 3.8 17.0": ["chole"], "12.6 8.1 7.8": ["motza"], "15.3 10.0 25.6": ["buffy"], "4.1 1.0 0.3": ["becom"], "14.4 20.8 9.4": ["abrading"], "12.4 27.9 9.3": ["nutballs"], "4.3 -2.1 7.6": ["breve"], "0.4 31.5 1.4": ["slanderer"], "16.8 -2.0 9.7": ["fullyear"], "6.8 6.5 19.5": ["corse"], "-1.5 1.3 0.7": ["valdecoxib"], "21.3 23.2 14.7": ["bootless"], "9.9 1.2 12.6": ["smokeshop"], "7.9 -1.6 14.5": ["soulstress"], "-8.5 9.2 11.9": ["pondok"], "-0.1 5.1 0.2": ["commitees"], "0.0 10.4 7.4": ["wetin"], "22.3 5.5 33.9": ["peapod"], "17.2 13.9 19.3": ["fiending"], "12.5 20.6 -0.6": ["coopting"], "-1.6 10.1 8.6": ["polaroids"], "0.7 25.4 6.6": ["complaisance"], "4.2 14.7 19.4": ["yellowness"], "3.8 3.2 12.1": ["norway"], "19.3 17.6 15.1": ["swang"], "-5.1 5.8 5.4": ["transpositions"], "9.2 15.1 26.6": ["pistils"], "21.0 12.8 18.8": ["quadrupedal"], "18.9 9.7 33.6": ["kedgeree"], "19.9 7.6 3.5": ["giddiest"], "20.4 3.3 14.7": ["spirally"], "14.8 12.8 10.9": ["cuddliness"], "5.2 17.4 9.8": ["scrummages"], "-1.6 13.0 16.2": ["trifluralin"], "11.7 9.4 -2.6": ["ensconcing"], "-3.0 7.9 9.1": ["deeksha"], "10.2 -2.0 2.1": ["promted"], "10.2 26.4 5.8": ["transfiguring"], "8.7 1.6 10.7": ["stonewashed"], "8.3 -2.2 17.9": ["pum"], "2.0 21.9 13.5": ["charcter"], "16.1 16.5 21.7": ["espaliered"], "7.2 23.7 2.7": ["unclenching"], "17.4 -1.3 1.7": ["cashstrapped"], "10.0 2.9 19.0": ["rollerblader"], "13.5 16.9 -1.9": ["unlikelier"], "12.0 14.5 14.4": ["ecomomy"], "4.4 10.5 1.3": ["ideate"], "1.0 5.0 9.7": ["heterozygotes"], "24.1 4.6 7.7": ["pyroelectric"], "-2.4 9.5 2.0": ["challaning"], "12.0 11.2 18.2": ["mestiza"], "2.1 12.7 11.5": ["masculinities"], "-2.7 -6.0 4.7": ["furfural"], "5.7 4.8 9.1": ["redcross"], "19.8 2.7 8.6": ["yestersday"], "-0.5 13.3 0.3": ["cytoprotective"], "5.6 -8.7 0.8": ["comple"], "-5.4 9.4 3.0": ["nontraumatic"], "2.4 8.5 9.2": ["tmrw"], "10.9 16.7 10.5": ["osx"], "6.4 9.7 11.8": ["midplane"], "1.7 1.5 17.1": ["challahs"], "2.6 -5.9 27.9": ["grassfed"], "5.6 9.2 12.1": ["orotund"], "4.5 5.0 7.2": ["somatostatin"], "6.2 9.1 9.8": ["ecomonic"], "0.9 3.1 9.5": ["trainors"], "9.6 14.0 12.9": ["rondavel"], "-2.1 -0.7 11.6": ["inseminations"], "-0.3 9.1 9.8": ["zon"], "4.3 17.3 15.0": ["malaprops"], "3.6 25.8 3.6": ["assailable"], "0.7 11.0 11.4": ["pesticidal"], "11.0 7.1 3.0": ["rechanneled"], "8.0 17.4 8.7": ["undeservingly"], "3.5 9.2 5.3": ["underclocked"], "-2.5 -1.4 1.9": ["teleservice"], "8.1 -3.2 13.7": ["exhibiters"], "9.7 5.5 8.9": ["microlithography"], "5.7 10.4 13.3": ["nmap"], "-3.2 11.0 16.2": ["unsuspended"], "-1.0 7.4 2.2": ["endevours"], "7.0 22.1 36.4": ["waterfowler"], "-10.0 8.7 15.5": ["thanksgivings"], "6.2 12.1 17.8": ["pansori"], "9.9 27.2 10.9": ["maquis"], "0.9 -2.1 9.5": ["urbanisations"], "9.2 11.8 18.6": ["rollick"], "6.4 9.1 25.0": ["angiosperm"], "21.7 7.3 2.4": ["screenless"], "11.1 2.0 34.0": ["wolfberries"], "0.9 5.5 14.3": ["pais"], "4.9 11.9 6.3": ["keypress"], "11.3 25.3 -2.5": ["stength"], "5.2 8.8 19.0": ["uva"], "15.2 9.7 18.6": ["cutsie"], "10.6 19.3 11.3": ["cemetaries"], "10.1 9.0 8.0": ["uplighting"], "13.9 14.7 20.4": ["postholes"], "2.7 11.1 6.4": ["ifthe"], "4.5 -1.4 3.8": ["akimat"], "22.3 0.8 18.7": ["zebrawood"], "1.8 7.7 20.1": ["silcrete"], "24.6 6.4 18.5": ["cheapy"], "-0.8 0.1 10.0": ["promotoras"], "11.9 -7.9 11.4": ["multigame"], "5.5 5.5 12.3": ["kampongs"], "1.6 9.6 12.2": ["hallux"], "6.1 6.0 16.9": ["labradoodles"], "15.4 8.9 19.1": ["dromedaries"], "10.5 3.7 8.4": ["hubub"], "14.3 10.7 6.8": ["orginated"], "5.8 5.4 12.3": ["antakshari"], "12.2 1.5 6.2": ["maxiumum"], "1.8 6.0 3.5": ["klebsiella"], "9.4 6.9 13.7": ["dumptrucks"], "10.3 2.8 10.3": ["bloco"], "20.9 7.8 2.3": ["stakeholdings"], "7.4 17.6 6.1": ["hg"], "7.2 11.8 7.9": ["accretes"], "13.0 14.0 13.8": ["straightjackets"], "12.6 16.4 11.8": ["fleabag"], "7.1 6.7 1.3": ["reportages"], "-0.6 23.1 13.3": ["heedful"], "3.4 21.3 -1.5": ["incitation"], "6.5 10.0 18.8": ["nanocages"], "11.2 12.3 11.7": ["matress"], "4.1 16.1 8.6": ["mispricings"], "4.8 4.4 6.1": ["bimbette"], "-0.9 -0.6 9.3": ["rodeoed"], "12.2 4.5 12.4": ["julle"], "4.1 27.2 -1.1": ["interahamwe"], "8.6 5.0 13.6": ["warblings"], "0.7 17.9 6.7": ["journalese"], "9.9 13.4 29.1": ["microcystis"], "9.2 6.1 11.3": ["maga"], "7.8 2.8 1.4": ["dilutionary"], "13.7 9.2 14.5": ["hiccough"], "-4.7 3.9 6.3": ["frontlist"], "4.4 10.3 7.6": ["blatherings"], "5.2 8.0 9.1": ["nulls"], "-7.6 3.2 0.7": ["onal"], "8.2 5.3 1.6": ["morgen"], "-2.9 -6.5 4.8": ["dih"], "-11.7 23.0 6.5": ["overborne"], "13.8 7.4 13.2": ["tener"], "-0.1 16.7 5.7": ["dissappeared"], "16.6 13.2 3.9": ["moralizers"], "3.9 10.0 3.5": ["powerpoints"], "12.9 9.6 10.1": ["verrry"], "2.4 9.7 12.0": ["nje"], "8.7 8.0 15.4": ["mannerist"], "9.3 13.3 17.4": ["breakingly"], "6.3 13.6 3.4": ["ignitor"], "1.6 7.0 12.7": ["racewalker"], "3.0 0.3 -2.8": ["immatics"], "1.5 -10.7 4.1": ["dds"], "7.9 10.2 10.9": ["goalmouths"], "-1.7 10.6 2.1": ["vot"], "1.9 16.5 3.3": ["outrebounds"], "-1.7 8.8 16.2": ["gentling"], "9.9 5.8 15.5": ["arnold"], "8.0 -1.7 19.2": ["feis"], "17.4 9.7 12.8": ["okes"], "6.6 12.9 8.0": ["rendevous"], "9.6 4.5 17.9": ["bulla"], "11.7 16.1 3.9": ["multip"], "2.7 15.8 9.1": ["statheads"], "2.6 7.1 10.7": ["overindulges"], "8.6 12.0 3.1": ["slumdogs"], "6.6 -3.1 0.9": ["fostamatinib"], "4.1 16.9 12.0": ["defectives"], "1.6 -0.4 4.6": ["qualfying"], "16.4 11.5 5.8": ["supercalifragilisticexpialidocious"], "9.7 11.3 11.6": ["hereditaries"], "4.7 11.4 9.9": ["scatterbrain"], "14.9 -4.4 5.3": ["toan"], "12.8 13.2 15.5": ["westie"], "13.8 12.7 31.0": ["swiftlets"], "1.9 24.0 12.1": ["overgeneralization"], "9.8 19.8 22.1": ["schmutz"], "-0.8 6.8 1.9": ["tafamidis"], "26.6 16.3 11.6": ["flunkey"], "-0.7 -1.4 0.4": ["perfrom"], "2.7 3.2 10.2": ["quiltmaking"], "11.0 8.2 2.6": ["medianet"], "22.6 16.7 17.5": ["goolies"], "-1.1 2.6 10.6": ["tenosynovitis"], "16.7 -2.7 8.0": ["spanky"], "-0.6 0.0 14.9": ["snowplay"], "-2.3 4.5 9.3": ["ening"], "12.9 16.9 8.0": ["bely"], "5.0 2.5 8.4": ["deliquent"], "7.2 3.5 15.5": ["leadline"], "10.1 -3.4 3.5": ["htt"], "-4.6 22.2 4.9": ["devoutness"], "0.7 15.9 -3.6": ["chanceries"], "8.4 1.3 -0.5": ["tapware"], "2.1 13.9 11.0": ["faceguard"], "-0.5 2.7 6.0": ["innundated"], "10.7 10.1 7.2": ["acton"], "16.6 12.8 13.0": ["alleluia"], "9.4 18.5 17.0": ["unhinges"], "12.8 17.6 8.6": ["flyblown"], "2.5 6.1 0.4": ["bioequivalency"], "1.7 7.8 7.2": ["dosimetric"], "-2.0 7.3 5.6": ["oversamples"], "3.2 -1.1 -1.2": ["ahe"], "15.3 15.2 24.8": ["drongo"], "2.5 14.3 3.8": ["channeler"], "-3.8 -5.1 6.7": ["enewsletter"], "-3.2 -1.7 -1.3": ["utc"], "4.7 26.6 10.5": ["hoseline"], "7.9 11.4 18.6": ["overeats"], "11.6 8.8 24.6": ["macrocarpa"], "9.5 -1.5 10.2": ["porterage"], "11.5 17.7 15.6": ["stonewaller"], "9.4 10.1 4.8": ["doolally"], "8.9 5.7 -13.7": ["workd"], "-6.0 0.8 11.0": ["ourt"], "14.4 8.6 11.7": ["sellling"], "1.1 11.6 7.0": ["chowkidars"], "-11.3 3.6 5.2": ["pegfilgrastim"], "8.0 4.5 16.2": ["perishability"], "18.8 5.5 14.5": ["chorines"], "9.5 1.1 6.8": ["indianapolis"], "-0.3 4.6 17.9": ["ichthyosis"], "0.6 7.6 -6.3": ["nuetral"], "2.5 23.2 13.6": ["dadagiri"], "4.0 13.0 9.3": ["gdb"], "6.6 7.8 23.7": ["overcooks"], "11.9 -4.7 3.1": ["juli"], "4.6 4.8 5.6": ["noncomplying"], "28.1 11.7 29.2": ["seedpod"], "-0.4 19.0 14.8": ["shirtlessness"], "4.6 0.7 10.2": ["epigenomics"], "9.1 7.0 7.7": ["crossmembers"], "15.9 28.9 14.8": ["exocet"], "2.3 2.3 9.9": ["euthanatized"], "-2.4 22.0 18.1": ["bjj"], "8.4 -0.3 6.3": ["photopolymer"], "9.1 1.6 5.6": ["pharmacognosy"], "-6.4 -0.2 5.4": ["pimecrolimus"], "-1.6 1.9 8.9": ["publichealth"], "13.2 4.5 39.9": ["guillemot"], "20.3 15.4 13.1": ["chinked"], "7.6 3.4 46.7": ["demersal"], "1.3 14.3 7.2": ["kutsi"], "5.4 5.2 19.5": ["zhong"], "10.6 14.4 19.0": ["sawyers"], "-2.9 5.9 5.6": ["ouse"], "-0.1 11.0 -1.6": ["wholetime"], "6.3 10.1 10.5": ["pele"], "4.3 -5.5 2.0": ["ej"], "-2.3 13.2 2.9": ["regenerations"], "13.7 1.2 18.5": ["plymouth"], "-8.7 3.8 8.6": ["anogenital"], "18.3 4.4 37.7": ["boilie"], "2.2 10.8 -3.0": ["crossbencher"], "0.1 8.1 13.8": ["transwomen"], "10.9 -11.4 6.9": ["iat"], "-3.9 12.2 3.6": ["saliently"], "10.7 12.9 13.7": ["regrew"], "0.3 2.7 7.8": ["colloquiums"], "8.8 20.7 9.9": ["coddler"], "17.0 6.2 18.3": ["suncatchers"], "21.1 21.7 13.9": ["brinks"], "1.6 10.9 6.4": ["easly"], "9.4 12.4 3.7": ["addresss"], "7.6 12.4 27.1": ["rewarm"], "6.6 28.0 23.0": ["shotgunners"], "2.2 -7.0 4.4": ["joh"], "5.9 12.6 4.1": ["curie"], "-2.2 4.5 6.2": ["recontesting"], "4.9 2.7 6.0": ["kwang"], "6.0 15.0 11.9": ["potholing"], "3.7 7.1 3.6": ["paystub"], "11.5 2.9 11.1": ["kilim"], "1.3 12.1 6.0": ["reson"], "12.4 -1.2 5.6": ["debossed"], "18.0 18.0 10.7": ["wunderbar"], "4.0 3.6 12.3": ["extremophile"], "9.1 5.7 33.5": ["gobi"], "10.2 19.2 17.0": ["mousers"], "7.9 34.7 12.7": ["conquerable"], "13.1 4.8 46.4": ["tataki"], "9.4 19.3 24.9": ["blowdowns"], "22.0 12.0 22.1": ["kerplunk"], "4.3 12.7 10.7": ["sangam"], "13.3 19.6 13.5": ["shylocks"], "9.0 18.9 5.3": ["jeapordy"], "0.7 5.4 -2.7": ["duely"], "16.7 11.0 11.8": ["heliostat"], "-4.6 5.3 10.2": ["propylthiouracil"], "-3.1 9.7 24.3": ["tabu"], "-2.3 -1.7 4.4": ["coronor"], "0.6 13.5 12.2": ["humectant"], "3.5 13.4 19.4": ["iya"], "16.5 11.2 10.8": ["sidereal"], "1.8 15.4 6.8": ["nieve"], "8.2 28.0 2.1": ["repressively"], "-7.7 14.5 6.9": ["peroxynitrite"], "0.3 20.4 -0.3": ["attitudinally"], "11.4 -0.2 -3.9": ["marketspace"], "4.4 17.3 10.9": ["jackassery"], "-1.3 2.9 10.0": ["tubist"], "9.9 25.0 10.2": ["menance"], "2.1 -0.5 -1.4": ["noteably"], "-0.9 8.6 15.4": ["mycorrhizal"], "7.1 17.0 14.8": ["mut"], "8.1 12.4 9.5": ["blackfellas"], "10.4 12.9 14.2": ["horseboxes"], "7.8 10.5 12.8": ["geomorphic"], "12.1 19.8 10.1": ["stalkerazzi"], "0.2 4.5 5.2": ["copyeditor"], "14.4 23.4 3.5": ["outmaneuvers"], "-0.2 1.3 1.9": ["gpf"], "27.0 18.7 17.0": ["hippogriff"], "2.5 2.0 21.4": ["whelping"], "0.1 12.5 7.2": ["redounded"], "8.0 1.3 2.9": ["camara"], "15.7 7.9 22.1": ["rickrack"], "1.0 -2.7 5.4": ["ihs"], "-0.3 6.6 13.1": ["alves"], "4.9 4.2 6.4": ["suspcious"], "18.1 23.7 10.7": ["shithouse"], "3.0 22.7 6.6": ["dumbfound"], "6.1 21.8 9.2": ["stemness"], "-2.3 16.2 8.3": ["artemisinins"], "12.9 4.2 13.8": ["fuera"], "13.2 9.0 20.4": ["dern"], "9.3 16.3 12.8": ["begats"], "-3.5 4.7 4.8": ["suraus"], "-5.1 15.0 11.3": ["underagers"], "0.6 20.2 9.8": ["dashcam"], "0.2 8.0 4.6": ["hypericin"], "4.7 2.6 10.1": ["atau"], "9.5 3.8 8.8": ["anhydrite"], "8.7 10.1 17.6": ["bhalo"], "6.8 3.4 -0.5": ["steamfitters"], "9.2 5.7 26.0": ["bayshore"], "1.9 23.4 9.4": ["bossism"], "3.6 21.6 9.5": ["loutishness"], "8.6 12.3 13.6": ["microlights"], "3.2 12.1 14.0": ["brassiness"], "8.9 4.3 11.3": ["jekk"], "11.1 -4.3 13.1": ["bolsa"], "2.5 7.9 14.3": ["dilapidations"], "-5.0 3.4 10.4": ["cantabile"], "-1.5 3.7 9.5": ["jucos"], "-1.0 2.0 11.2": ["flatpicking"], "14.0 11.3 17.8": ["fancily"], "4.2 22.7 3.1": ["unsuspicious"], "2.1 6.1 3.3": ["wolfhesse"], "17.6 15.9 20.1": ["pittosporum"], "5.5 15.2 17.0": ["polygynous"], "-0.5 4.3 7.7": ["spondylosis"], "7.1 7.9 15.1": ["befo"], "2.8 1.4 15.6": ["montgomery"], "4.3 12.5 6.8": ["repartees"], "16.2 17.0 15.2": ["snookering"], "4.0 -1.7 8.8": ["inglese"], "10.0 5.4 17.4": ["palmy"], "-1.2 9.4 4.9": ["contemnors"], "7.8 4.6 13.6": ["recoated"], "6.0 13.2 27.7": ["rudbeckias"], "7.3 6.4 3.8": ["offier"], "11.3 8.5 25.4": ["nok"], "-3.6 14.3 9.2": ["ishq"], "8.5 1.2 12.6": ["slackline"], "18.6 11.7 13.8": ["ickle"], "14.8 1.0 8.7": ["emgs"], "9.8 3.4 22.1": ["cavies"], "3.8 8.0 8.2": ["percussively"], "-0.5 0.2 18.1": ["pmto"], "1.5 14.6 10.2": ["kahin"], "-2.2 23.7 14.2": ["nonaction"], "7.9 12.3 19.4": ["bargeboards"], "9.2 2.9 20.1": ["narrowboats"], "-2.5 18.7 14.4": ["reraises"], "3.8 4.8 18.4": ["fromm"], "0.1 5.6 23.5": ["brevis"], "11.5 2.3 -1.9": ["equinux"], "-4.7 6.0 6.1": ["antiemetics"], "-3.7 6.8 6.3": ["disabilites"], "4.6 17.0 3.6": ["comon"], "4.8 5.6 11.6": ["forall"], "3.0 9.9 13.0": ["beggin"], "-6.8 11.1 2.3": ["astrocytomas"], "3.0 5.3 12.3": ["lara"], "7.0 11.0 14.4": ["posix"], "16.2 9.3 18.4": ["chupinazo"], "7.9 12.7 6.3": ["sicked"], "7.6 11.1 9.2": ["mplayer"], "5.6 4.1 4.0": ["globulin"], "4.6 9.1 14.9": ["albite"], "15.0 15.5 10.6": ["palookas"], "8.2 15.7 8.2": ["energiser"], "-0.3 1.5 7.2": ["aimags"], "8.5 6.2 5.8": ["underserving"], "3.1 21.6 6.0": ["stovepiping"], "-2.2 5.7 12.3": ["operon"], "10.1 6.1 13.4": ["fishtails"], "1.0 16.3 5.1": ["engrain"], "4.3 12.5 4.8": ["femtos"], "17.7 1.2 19.0": ["bacchanals"], "19.5 9.4 36.7": ["takoyaki"], "12.8 -7.6 11.5": ["comparedwith"], "0.6 1.1 8.2": ["transaxles"], "-0.7 10.3 12.8": ["poice"], "8.2 14.4 10.3": ["miserablist"], "-0.0 -7.8 9.6": ["openhouse"], "8.5 -1.9 8.0": ["ewaste"], "12.9 10.3 27.4": ["cardoon"], "11.5 11.6 14.5": ["depilation"], "10.5 16.9 29.7": ["barberries"], "2.8 7.9 1.1": ["breif"], "10.4 2.9 13.7": ["punksters"], "9.1 14.1 17.9": ["dealy"], "-2.9 -1.1 -3.9": ["abbreviates"], "-4.5 6.4 1.0": ["cardioplegia"], "9.4 5.9 1.7": ["plauged"], "12.1 14.9 15.6": ["grody"], "5.8 15.3 6.0": ["mlmintampa"], "3.5 15.7 9.3": ["kvetches"], "21.8 11.1 4.1": ["mightly"], "15.0 5.7 0.1": ["ueber"], "22.2 7.1 26.2": ["splodges"], "5.5 5.6 12.9": ["jaa"], "-5.4 15.2 0.3": ["coversation"], "-5.4 6.5 7.8": ["novations"], "14.5 6.5 14.1": ["lathing"], "4.5 13.0 12.0": ["sallyport", "javawebdeveloper"], "3.2 14.9 18.0": ["luffed"], "3.0 -0.5 11.5": ["ileal"], "10.1 4.4 -1.8": ["shoppable"], "8.8 9.6 23.4": ["lepidopterist"], "0.8 10.1 15.5": ["ginagawa"], "12.2 2.9 12.1": ["criss"], "3.4 2.2 12.3": ["bandpass"], "9.2 18.0 8.2": ["cryptograms"], "15.4 13.0 21.7": ["rippable"], "12.2 6.8 6.6": ["telepathology"], "10.2 15.3 9.5": ["reputably"], "-4.0 -0.2 15.0": ["marsanne"], "-3.4 11.4 -2.6": ["reffering"], "2.8 3.6 -3.8": ["repsonsible"], "5.4 17.9 9.9": ["gerunds"], "8.2 9.0 17.7": ["octahedron"], "6.4 6.2 18.8": ["masterchef"], "11.3 -4.9 11.4": ["psm"], "1.2 5.7 10.2": ["astringents"], "15.6 20.4 23.8": ["piratey"], "2.0 2.3 8.6": ["fueron"], "-3.9 4.4 4.6": ["myelomeningocele"], "10.8 8.0 7.5": ["punkabilly"], "3.3 8.2 1.8": ["invalidly"], "8.9 -0.2 -1.5": ["billpay"], "10.8 5.6 0.5": ["repoted"], "3.8 9.9 2.5": ["gazetteers"], "-4.0 6.5 -2.7": ["awar"], "9.5 3.4 25.8": ["finn"], "14.2 10.2 13.5": ["shittier"], "12.6 20.4 5.3": ["virtuousness"], "11.7 -1.8 4.7": ["spunmelt"], "7.6 21.1 8.5": ["anonymizers"], "-1.5 19.9 5.0": ["ineptitudes"], "5.8 -2.6 6.5": ["sinced"], "-10.9 1.1 -1.6": ["neuroleptic"], "17.5 14.8 29.3": ["loris"], "3.2 -0.3 8.0": ["kvelling"], "2.5 9.8 3.7": ["convice"], "1.8 3.8 2.7": ["runnerups"], "14.1 8.9 15.7": ["overbanked"], "-3.8 2.5 5.2": ["exemptive"], "1.7 18.5 19.2": ["highspots"], "20.3 10.9 10.2": ["centrepoint"], "4.0 7.5 4.5": ["yl"], "16.9 17.2 7.0": ["lackies"], "8.2 1.4 8.9": ["sizeably"], "5.4 -7.0 2.4": ["ahr"], "13.1 16.7 9.9": ["liberationists"], "16.1 1.1 21.6": ["widthwise"], "3.7 18.2 1.3": ["inductively"], "4.2 1.4 6.6": ["preintegrated"], "12.1 15.4 13.9": ["corraling"], "-7.6 5.6 3.5": ["elopements"], "11.6 10.8 15.0": ["psn"], "-2.6 5.8 9.5": ["reoffends"], "15.0 14.0 7.5": ["dumbphone"], "3.9 27.6 15.1": ["fungos"], "15.7 3.9 17.6": ["ular"], "17.3 6.1 15.8": ["pouter"], "16.6 25.2 9.0": ["idiocracy"], "11.3 20.8 10.1": ["gunport"], "-0.2 9.8 13.7": ["photobleaching"], "-5.1 3.6 10.3": ["proteoglycan"], "-12.3 7.8 2.5": ["periprocedural"], "-1.9 1.3 14.5": ["iqamas"], "17.7 5.2 13.4": ["accordioned"], "-0.5 -0.0 13.9": ["underrotated"], "1.6 14.9 13.4": ["cadherins"], "10.1 9.1 3.2": ["refounding"], "18.7 11.4 15.2": ["boop"], "3.0 3.5 17.3": ["tussar"], "9.6 6.5 13.2": ["inurl"], "3.1 6.2 18.2": ["hotwalker"], "3.1 10.2 0.2": ["annivesary"], "-2.9 12.3 8.0": ["mosfet"], "7.5 1.0 16.5": ["mercados"], "-3.7 18.2 0.5": ["incorrupt"], "7.7 11.6 12.0": ["huskily"], "4.2 10.1 16.5": ["genteelly"], "17.1 10.6 33.8": ["bankside"], "1.4 8.2 15.2": ["homogenously"], "1.8 3.5 4.7": ["newschannel"], "8.4 7.0 10.6": ["uncoded"], "2.1 18.2 10.8": ["acerbity"], "2.2 -2.4 0.5": ["heptaminol"], "6.6 7.1 9.2": ["assez"], "3.1 12.1 6.2": ["disatisfied"], "9.9 -1.1 8.9": ["mainlined"], "25.8 5.9 2.1": ["larget"], "11.2 0.0 5.3": ["acitivity"], "4.3 10.0 18.5": ["ouchy"], "13.1 1.3 -2.5": ["industrie"], "7.4 4.1 9.6": ["geomembrane"], "8.0 7.8 4.4": ["buycott"], "15.0 14.5 14.4": ["jiggering"], "3.2 5.9 11.2": ["fanmail"], "-3.6 39.1 4.2": ["fireteam"], "6.1 14.0 11.9": ["nameserver"], "7.8 16.4 17.1": ["womanliness"], "1.9 -5.0 5.1": ["noneducational"], "-5.3 -0.9 15.2": ["kahapon"], "4.5 4.7 5.4": ["overvaluations"], "4.7 8.0 2.6": ["dissector"], "11.1 6.1 9.1": ["yohimbe"], "11.2 9.1 13.4": ["bangla"], "8.2 10.8 5.7": ["formating"], "27.9 10.4 19.0": ["skeeball"], "11.1 10.2 10.6": ["stupors"], "13.3 3.4 20.9": ["colada"], "8.2 7.5 3.7": ["cabover"], "13.1 4.3 11.8": ["regassification"], "-1.7 9.8 7.5": ["tumoral"], "7.7 10.7 15.5": ["plata"], "3.6 5.6 1.3": ["cherrypicked"], "9.4 0.6 1.5": ["distribbed"], "6.1 11.1 4.9": ["highrisk", "amassment"], "14.6 5.5 19.6": ["biathlons"], "6.0 11.3 14.4": ["inholdings"], "1.5 9.9 -4.1": ["chages"], "6.4 5.3 6.3": ["mislay"], "5.8 10.4 15.1": ["dancelike"], "-1.8 11.9 15.4": ["cyanotic"], "1.4 9.4 35.4": ["poult"], "7.6 5.1 13.0": ["labourious"], "8.5 7.5 8.4": ["overindebted"], "-2.2 5.4 12.4": ["presbycusis"], "-4.3 1.2 -3.3": ["assisant"], "-1.1 3.7 0.1": ["consectutive"], "14.4 12.7 11.4": ["axion"], "-0.9 4.6 13.2": ["alkalizing"], "6.2 3.2 7.3": ["overmolded"], "8.7 -1.5 26.0": ["chocolat"], "0.7 12.8 14.6": ["boatlength"], "4.4 14.7 2.7": ["preachments"], "5.5 -1.9 9.1": ["headwalls"], "-0.6 4.5 20.0": ["nontasters"], "-2.3 -4.6 -0.0": ["radiotherapeutic"], "6.5 -5.1 15.9": ["resalable"], "7.6 11.2 10.7": ["twills"], "9.3 3.7 3.7": ["dotmobi"], "12.7 25.7 11.1": ["schizophrenically"], "3.5 29.0 16.7": ["flashbang"], "-1.7 19.0 5.8": ["minimalized"], "9.0 12.0 36.7": ["whaleboat"], "4.4 -3.3 1.7": ["cae"], "-0.8 7.0 1.4": ["timestamped"], "-0.5 15.9 -0.2": ["thoug"], "8.6 10.3 0.2": ["perenial"], "13.8 11.2 22.8": ["magentas"], "3.0 8.9 10.8": ["portamento"], "-3.0 6.7 8.1": ["excessed"], "3.4 -5.4 -0.8": ["energie"], "-7.8 9.5 -0.1": ["microbleeds"], "8.0 -1.7 9.6": ["bulldogger"], "14.8 4.7 14.3": ["yas"], "12.4 10.1 10.9": ["nsw"], "18.6 2.6 32.2": ["cakelike"], "-0.8 20.8 -2.8": ["renditioned"], "-2.2 4.3 7.3": ["iridoids"], "4.5 5.1 2.4": ["enchance"], "-5.6 0.9 -1.2": ["sufentanil"], "16.2 13.5 33.2": ["gyrfalcon"], "8.1 23.7 17.3": ["bollix"], "1.3 0.9 6.5": ["biomechanic"], "-1.2 3.6 6.0": ["historia"], "6.4 8.6 11.7": ["spect"], "15.0 18.7 16.1": ["underslung"], "4.5 3.6 17.3": ["spunkier"], "11.9 11.4 12.9": ["denarius"], "2.1 23.2 9.8": ["unaccepting"], "13.0 -3.7 43.9": ["eelpout"], "5.0 6.9 12.9": ["pehle"], "9.4 22.0 7.3": ["colonialization"], "5.0 12.0 6.3": ["provinciality"], "2.5 7.6 5.0": ["disincorporate"], "5.4 7.2 4.7": ["apocrypha"], "4.7 18.7 17.3": ["hallows"], "10.0 2.5 8.8": ["haber"], "-8.2 21.0 -6.1": ["legalist"], "14.9 6.0 30.2": ["galbi"], "-1.0 3.1 9.8": ["coproduct"], "3.2 12.3 11.7": ["muc"], "12.5 12.9 2.2": ["realworld"], "-1.6 11.3 3.0": ["rechanneling"], "10.6 32.3 13.0": ["unexpecting"], "11.6 2.4 24.0": ["trulli"], "1.9 3.2 -4.6": ["bsp"], "5.6 13.3 12.1": ["blancos"], "2.8 10.1 5.7": ["gta"], "-5.3 5.3 -0.7": ["lka"], "-0.6 16.1 0.9": ["underrates"], "6.2 6.4 16.0": ["mitch"], "1.5 1.3 11.7": ["negociants"], "11.7 4.5 2.4": ["governmment"], "12.0 10.7 21.9": ["gallus"], "-0.5 9.1 2.8": ["lotof"], "1.5 5.8 2.2": ["jathedar"], "7.6 19.5 23.1": ["expectoration"], "4.1 -0.3 18.2": ["riverboarding"], "5.3 20.7 5.1": ["confederated"], "2.0 8.2 -2.8": ["onhis"], "-2.7 10.0 0.4": ["toldreporters"], "9.1 7.6 30.1": ["samp"], "14.4 16.1 15.7": ["telltales"], "16.9 16.1 14.7": ["snugs"], "-8.5 3.1 11.3": ["methodologic"], "12.6 4.2 15.3": ["fermentors"], "5.5 -2.5 5.7": ["areexpected"], "-6.0 6.2 2.8": ["umra"], "2.2 40.0 8.4": ["hezbollah"], "10.4 16.0 8.9": ["nzherald"], "3.2 28.5 1.5": ["disorganize"], "11.6 11.2 24.3": ["macerating"], "6.4 8.4 4.8": ["tobuild"], "-7.9 -0.4 1.4": ["tubectomy"], "4.5 7.0 8.8": ["remaps"], "2.1 13.8 11.5": ["politi"], "7.6 1.8 15.2": ["pubbing"], "12.2 13.1 4.8": ["esports"], "-8.4 10.7 6.4": ["subparts"], "16.7 32.3 2.4": ["cyberterrorists"], "20.8 4.5 10.0": ["chilhood"], "3.2 5.6 45.5": ["tonging"], "10.1 6.6 21.1": ["cocoyam"], "3.5 9.7 18.7": ["berbere"], "7.6 6.1 1.6": ["quanp"], "-1.1 5.3 1.4": ["cobiprostone"], "8.7 -1.7 8.7": ["jewerly"], "4.5 10.9 12.1": ["nanochannels"], "19.1 -0.0 6.3": ["smartboard"], "2.0 5.0 14.5": ["filopodia"], "1.8 22.4 17.7": ["jhum"], "5.9 12.8 -1.5": ["asthey"], "10.8 16.5 11.2": ["baaad"], "5.1 -2.9 31.7": ["rockling"], "14.5 3.4 16.0": ["sexagenarians"], "10.7 13.1 11.9": ["megazoom"], "3.6 6.1 10.6": ["cruiseline"], "19.6 13.9 14.6": ["dustbowls"], "0.0 -1.3 -0.8": ["embolisation"], "-3.0 7.6 7.6": ["benga"], "16.2 2.8 21.3": ["icepacks"], "2.2 2.3 13.8": ["osteophytes"], "8.6 7.8 31.5": ["kibbe"], "10.9 10.8 19.8": ["syrinx"], "11.6 16.8 10.4": ["kotaku"], "21.1 9.4 3.3": ["apeing"], "10.2 10.3 12.2": ["haterade"], "17.5 9.2 24.2": ["unwatered"], "0.4 6.8 6.5": ["tetramer"], "8.8 13.4 16.5": ["tranquilise"], "3.5 1.6 6.8": ["cosmetician"], "1.9 15.0 6.8": ["sacramentally"], "-0.8 5.3 2.3": ["neuromotor"], "7.7 6.4 8.7": ["underflow"], "4.0 -6.6 8.0": ["chuh"], "6.9 0.8 17.9": ["mori"], "8.6 1.8 9.3": ["valueadded"], "17.5 10.5 15.7": ["boardriders"], "5.8 9.6 6.0": ["aiff"], "10.7 -1.6 4.0": ["superblocks"], "3.2 16.9 13.5": ["slopey"], "-7.0 -4.5 20.8": ["pinhookers"], "-3.9 0.5 7.6": ["nna"], "-2.3 -4.5 3.2": ["filmings"], "1.3 5.9 -0.6": ["acti"], "21.3 7.6 9.5": ["arcadia"], "-0.2 10.8 2.8": ["parasomnias"], "15.5 5.1 29.7": ["kapa"], "-10.2 12.7 -1.9": ["speaches"], "6.4 24.9 12.4": ["escapists"], "13.0 7.2 8.2": ["exobiology"], "2.6 11.7 17.8": ["belayed"], "25.0 15.1 18.9": ["covetously"], "1.7 13.4 5.5": ["liker"], "-0.6 16.6 8.7": ["riflescopes"], "-6.1 4.1 7.1": ["underenrolled"], "13.3 -0.9 5.5": ["afull"], "16.3 -5.0 1.2": ["lastmonth"], "5.2 15.2 17.0": ["migra"], "1.4 1.6 -0.8": ["thetreatment"], "3.2 8.4 3.7": ["systemization"], "7.6 12.4 5.3": ["sparsest"], "2.7 3.4 3.5": ["sterilant"], "-8.7 14.4 8.3": ["mupirocin"], "14.6 19.9 7.5": ["autocorrect"], "1.5 -0.6 6.8": ["multicores"], "6.6 10.7 11.4": ["pepsin"], "-1.5 12.8 1.8": ["elction", "exhanged"], "5.1 3.6 10.4": ["bioleach"], "5.1 6.2 3.3": ["trouped"], "4.7 8.6 11.2": ["illegibly"], "3.6 5.4 13.9": ["foldback"], "9.9 18.1 7.1": ["congressmembers"], "6.4 13.0 41.8": ["sewin"], "2.9 12.4 10.9": ["pujari"], "5.9 15.0 14.2": ["anythin"], "-0.5 17.6 5.5": ["purposing"], "11.7 16.1 4.0": ["intersectoral"], "-1.6 7.0 16.7": ["pagka"], "-0.6 15.3 16.2": ["marty"], "14.4 8.8 13.1": ["chiseler"], "8.3 6.0 3.7": ["technolgies"], "2.1 8.7 8.6": ["shticky"], "1.0 -5.7 6.2": ["nikethamide"], "8.4 27.0 9.6": ["abhorrently"], "7.3 0.4 11.7": ["essere"], "-2.3 -0.4 -3.7": ["postitive"], "2.0 -4.6 1.8": ["noncallable"], "7.0 19.4 3.3": ["sensate"], "10.4 12.3 13.4": ["rrr"], "10.3 -5.9 15.8": ["supercalendered"], "18.6 -1.3 20.3": ["bikinied"], "8.2 2.6 19.0": ["derful"], "4.7 3.8 -4.1": ["retransfer"], "13.5 15.8 16.7": ["nonethless"], "4.2 9.0 9.8": ["mikel"], "5.8 8.8 8.7": ["perspires"], "11.4 11.2 3.2": ["shoddiest"], "3.3 17.5 6.4": ["outsailed"], "5.2 12.9 11.1": ["quod"], "17.5 10.2 22.6": ["gopuram"], "-0.9 7.1 8.1": ["antegrade"], "3.3 4.8 24.4": ["spritzy"], "3.9 18.1 12.8": ["leadfoot"], "-7.2 6.5 2.8": ["opiod"], "0.1 5.9 11.9": ["purulent"], "24.2 4.0 19.7": ["snippers"], "9.4 9.0 -1.8": ["concretization"], "5.4 -2.8 12.3": ["fraktur"], "2.6 5.1 9.2": ["abel"], "7.7 8.7 32.2": ["gundalow"], "9.8 11.2 15.2": ["dognappers"], "1.9 4.8 2.2": ["insufficent"], "0.8 12.5 13.9": ["timeconsuming"], "-3.3 13.0 10.4": ["milieux"], "10.1 26.3 13.8": ["virii"], "14.2 24.3 5.4": ["handgrenades"], "5.1 2.3 9.7": ["muscovite"], "9.8 -4.1 6.5": ["yearon"], "16.3 13.6 26.7": ["tanager"], "5.1 10.4 8.6": ["ostentatiousness"], "8.0 5.3 8.9": ["orth"], "-0.6 4.7 6.6": ["milliohm"], "3.5 8.0 7.0": ["dermoscopy"], "14.8 1.3 25.5": ["chinois"], "10.7 1.2 4.5": ["collator"], "9.7 5.1 2.4": ["salesforces"], "0.1 17.2 11.0": ["austenite"], "22.2 9.8 1.4": ["pitmen"], "0.2 2.3 3.9": ["multidose"], "12.3 13.5 11.5": ["irradiates"], "0.8 12.0 9.2": ["ruckwork"], "2.7 10.1 14.4": ["dumpoff"], "4.7 5.3 4.8": ["nanocoating"], "8.3 15.2 10.9": ["viewscape"], "12.3 6.5 0.3": ["fraudulant"], "11.5 -0.6 3.0": ["reprofiled"], "0.7 3.8 0.4": ["dualised"], "10.2 33.7 16.7": ["fighers"], "-1.4 -6.2 16.2": ["ngayong"], "-0.3 8.6 16.3": ["pali"], "14.9 4.9 17.2": ["suckles"], "8.4 21.1 14.3": ["segways"], "6.0 3.5 21.6": ["pepe"], "0.3 8.4 4.3": ["availiable"], "8.8 3.9 6.9": ["nuevos"], "4.3 4.0 0.2": ["adhd"], "-0.6 19.7 -2.0": ["rapports"], "15.3 10.0 2.4": ["maximizer"], "-2.1 12.6 7.3": ["diasporan"], "-0.7 6.5 12.6": ["optionable"], "-1.7 13.0 8.6": ["precuneus"], "14.7 6.9 23.2": ["hina"], "8.4 5.2 21.3": ["marketgoers"], "6.7 8.0 7.4": ["ustream"], "1.0 2.0 21.3": ["phane"], "17.4 6.0 2.7": ["thathas"], "0.1 -4.3 3.2": ["agr"], "8.6 10.4 22.9": ["calendulas"], "13.6 6.4 2.8": ["releaser"], "-2.4 22.0 8.9": ["fulness"], "-4.7 14.3 9.2": ["listenings"], "1.2 3.8 0.7": ["weeken"], "9.7 5.0 13.8": ["blat"], "4.4 -1.3 2.5": ["endoluminal"], "13.0 12.1 8.8": ["mountebank"], "-0.7 10.9 9.2": ["monolog"], "32.5 17.4 19.8": ["splatted"], "7.9 9.5 27.7": ["orientalis"], "18.0 14.3 25.4": ["billabongs"], "11.7 10.0 15.9": ["zy"], "11.5 5.6 6.5": ["kva"], "0.8 9.1 7.6": ["padmapreetham"], "1.2 4.9 1.8": ["rightholders"], "9.0 16.8 12.3": ["stairmaster"], "3.2 4.1 15.0": ["streetwalking"], "-5.1 7.2 6.8": ["jis"], "0.7 6.6 8.4": ["sess"], "4.0 13.2 7.5": ["titrating"], "1.3 21.0 11.7": ["comfortableness"], "-0.3 -6.9 8.4": ["coe"], "2.8 11.3 15.2": ["hornier"], "6.8 1.3 5.4": ["costumier"], "4.3 8.6 10.5": ["archicad"], "9.8 -2.7 -2.9": ["publica"], "11.7 2.1 -0.2": ["phling"], "5.8 20.4 8.1": ["corrosively"], "3.3 6.1 8.1": ["ductless"], "-3.5 5.6 8.1": ["nonincumbent"], "-0.0 -1.7 0.3": ["pased"], "18.6 -3.9 3.6": ["previoulsy"], "6.2 2.4 8.0": ["nuovo"], "11.7 0.9 17.4": ["coonhounds"], "10.3 23.6 10.2": ["kinesis"], "11.5 22.5 -0.8": ["nonperson"], "5.7 43.2 3.3": ["basterds"], "6.6 32.0 2.1": ["demagogically"], "-5.9 13.9 5.2": ["faqih"], "15.7 5.0 10.9": ["drivethru"], "-0.3 12.6 3.2": ["prespective"], "11.6 21.6 13.1": ["prigs"], "4.3 14.2 10.6": ["snobbishly"], "12.9 8.8 12.1": ["bimetal"], "7.4 14.1 15.8": ["chamfering"], "15.7 5.6 30.4": ["coprolite"], "7.5 16.1 23.6": ["cavefish"], "0.4 3.8 22.6": ["ecoregion"], "-4.9 -2.4 -0.2": ["methodologist"], "8.4 -7.3 6.3": ["aproved"], "11.5 22.6 5.0": ["destoryed"], "4.4 6.9 24.4": ["parboiling"], "18.7 14.2 5.5": ["anticorporate"], "6.8 9.1 -2.3": ["ldquo"], "19.7 11.2 31.0": ["quacker"], "3.8 7.9 17.8": ["waterbus"], "-2.4 16.4 2.8": ["obligee"], "3.5 -6.0 1.1": ["provi"], "11.9 14.1 8.9": ["butterfingered"], "10.7 2.9 11.4": ["salas", "tacs"], "-5.2 6.8 6.2": ["infanticides"], "15.4 11.6 -1.7": ["searchs"], "6.5 2.6 14.3": ["siete"], "5.2 13.5 12.1": ["kickdown"], "-5.0 8.4 6.7": ["establishers"], "15.4 9.5 10.5": ["beveling"], "6.4 15.1 13.4": ["rasper"], "8.5 12.1 1.2": ["diamantaire"], "7.9 10.6 6.5": ["repressurized"], "6.2 -2.4 7.6": ["auditeria"], "22.9 10.6 6.3": ["unglue"], "18.1 15.6 14.5": ["chunder"], "2.4 5.5 14.9": ["deaccession"], "17.9 4.8 11.6": ["midquarter"], "19.0 7.2 16.5": ["chix"], "-2.9 3.0 2.2": ["changeout"], "0.6 -1.3 0.9": ["charing"], "-1.4 12.3 8.9": ["coquetry"], "-6.7 1.1 16.7": ["growns"], "12.9 7.2 10.7": ["dweebish"], "-4.9 -0.4 9.3": ["sesion"], "11.9 8.2 12.6": ["blackpool"], "1.9 3.4 -2.3": ["webzines"], "-1.8 4.3 12.9": ["diquafosol"], "7.1 29.9 15.2": ["revenges"], "-5.1 3.5 14.5": ["lalo"], "2.4 12.4 4.6": ["efficiences"], "4.5 11.6 1.0": ["otehr"], "5.2 9.0 25.9": ["pericarp"], "17.1 4.0 2.3": ["brandnames"], "5.2 0.5 17.4": ["prestorm"], "5.3 19.1 8.2": ["multileveled"], "-3.1 10.6 10.0": ["coexistent"], "7.8 7.6 9.6": ["reminiscient"], "7.4 3.1 13.7": ["triathalons"], "7.4 4.7 28.2": ["downlisted"], "6.6 3.4 15.3": ["carabineer"], "3.4 15.1 11.7": ["descriptives"], "7.0 3.4 10.5": ["mailable"], "8.8 20.0 -1.6": ["forcedly"], "17.8 12.1 4.1": ["fructifies"], "6.6 9.7 9.1": ["glamorisation"], "1.8 4.1 2.1": ["underly"], "-7.4 12.2 3.0": ["restaff"], "4.7 12.6 13.4": ["prevacid"], "9.5 12.5 4.1": ["leptons"], "5.1 15.2 14.6": ["brianbwb"], "10.4 14.7 41.8": ["goldeneye"], "2.8 16.2 20.7": ["thm"], "-0.7 6.9 2.2": ["thanthe"], "-0.9 -13.7 -2.5": ["ihk"], "10.2 14.0 9.6": ["spectroscope"], "0.1 10.3 -1.5": ["detribalised"], "9.6 7.3 19.9": ["floribundas"], "15.2 8.4 10.2": ["simpered"], "7.5 4.2 15.4": ["angklung"], "6.4 14.6 6.6": ["winamp"], "3.2 6.1 21.7": ["lua"], "9.6 -3.6 6.4": ["offsites"], "12.4 6.1 22.6": ["maraschino"], "1.9 2.6 22.2": ["bhat"], "7.6 7.8 16.4": ["weas"], "-3.1 -4.4 -3.7": ["garned"], "13.7 13.6 8.5": ["pions"], "4.5 9.8 1.8": ["independantly"], "6.4 17.2 8.7": ["astrometry"], "13.6 30.5 6.7": ["jetfighter"], "12.5 2.3 2.3": ["demultiplexer"], "11.9 7.2 27.4": ["rancheros"], "12.8 17.3 16.0": ["snits"], "16.5 14.7 17.2": ["merkin"], "4.1 11.9 13.2": ["baconstang"], "12.3 15.3 15.6": ["polders"], "5.1 24.8 -1.0": ["abased"], "-3.6 11.6 8.6": ["convience"], "2.1 1.3 8.4": ["reprographers"], "3.0 -3.1 6.2": ["subsites"], "-3.1 5.5 8.0": ["sacroiliac"], "6.7 20.7 8.5": ["catholicism"], "17.8 13.1 16.2": ["cheesing"], "11.7 10.0 10.0": ["paramotor"], "10.1 16.5 14.4": ["carwin"], "-12.6 -2.3 -4.1": ["forf"], "5.3 -2.2 10.7": ["clair"], "0.6 0.9 13.0": ["semigloss"], "6.4 4.6 15.9": ["ethnologists"], "1.5 3.3 14.1": ["gara"], "8.4 14.0 9.9": ["kilotonne"], "4.2 -3.4 2.7": ["evertiq"], "5.7 13.9 5.1": ["manoeuvered"], "7.5 13.4 15.4": ["grr"], "6.6 6.1 29.3": ["pepperpot"], "8.7 9.5 7.5": ["interweaved"], "3.6 1.3 9.3": ["sigmoid"], "-2.0 3.0 -3.9": ["chairmans"], "29.7 10.9 12.8": ["juddered"], "9.7 10.8 9.7": ["pubescence"], "9.1 9.2 5.7": ["townlands"], "13.8 17.8 13.1": ["tremulously"], "4.5 17.8 14.5": ["salman"], "10.5 17.9 14.6": ["yoru"], "16.1 1.5 7.7": ["thirtyish"], "6.1 5.6 16.7": ["dioritic"], "9.6 14.5 11.3": ["shooutout"], "6.1 15.1 12.9": ["drydown"], "6.9 6.4 27.8": ["clivia"], "2.8 6.7 3.3": ["ganz"], "14.1 -0.1 9.2": ["soleil"], "15.9 18.8 9.0": ["reproachfully"], "3.7 16.1 5.4": ["documenter", "occulted"], "21.1 11.3 23.5": ["davits"], "4.8 12.7 9.7": ["famewhore"], "-4.2 14.2 4.4": ["frustated"], "2.6 4.8 6.6": ["sprightlier"], "1.9 -1.1 6.5": ["unblind"], "5.4 11.6 12.5": ["antiserum"], "7.3 20.6 6.5": ["undebatable"], "0.1 21.4 -2.1": ["politicalization"], "-2.7 5.2 0.9": ["haart"], "3.8 15.4 7.5": ["priviliged"], "-10.3 6.1 1.3": ["relected"], "4.3 2.9 5.3": ["finace"], "3.9 1.3 9.6": ["mira"], "6.2 6.8 13.3": ["laughfest"], "10.1 4.9 11.8": ["mildy"], "5.9 8.2 14.5": ["juvenille"], "-5.8 -0.1 4.5": ["carboxyhemoglobin"], "7.7 -2.9 8.0": ["andone"], "2.1 4.4 6.0": ["mbox"], "2.6 -4.9 -0.2": ["voix"], "6.2 2.8 10.4": ["hilltowns"], "2.1 7.6 3.6": ["bageled"], "2.9 13.3 14.1": ["protag"], "4.8 34.4 4.6": ["bridgeheads"], "14.9 10.7 18.9": ["mandrels"], "6.1 10.5 13.8": ["buf"], "-9.5 21.5 5.2": ["normatively"], "-11.3 14.6 2.3": ["talmidim"], "13.4 27.1 16.0": ["hyperaggressive"], "-1.6 15.2 10.5": ["faceshields"], "-6.1 -0.3 6.3": ["signi"], "15.7 7.5 12.6": ["belgian"], "0.8 24.0 6.2": ["gnosticism"], "11.1 -0.7 19.7": ["satinwood"], "5.6 7.2 8.0": ["sermonette"], "9.8 18.6 1.3": ["parodists"], "7.7 19.7 8.8": ["cyphers"], "8.1 4.8 16.3": ["blushers"], "1.9 17.4 12.2": ["toolholder"], "0.0 3.3 8.4": ["disincentivise"], "11.8 15.5 6.5": ["lightgun"], "-3.1 -2.5 1.2": ["perfusionist"], "14.3 12.6 4.1": ["bungie"], "10.4 5.3 7.3": ["refinishes"], "5.9 6.2 1.3": ["intracompany"], "-2.5 -2.7 22.7": ["chuen"], "4.2 12.6 13.2": ["rishi"], "2.9 1.4 6.7": ["premeire"], "1.3 -6.3 7.0": ["bicounty"], "7.9 6.0 6.8": ["justicia"], "11.7 0.4 14.1": ["preceed"], "3.7 15.6 0.8": ["astigmatic"], "17.9 -3.8 25.9": ["axolotls"], "11.4 6.7 15.9": ["foresting"], "5.1 1.1 7.5": ["glyconutrients"], "-6.0 5.4 -1.0": ["phonophobia"], "4.6 0.0 5.3": ["rei"], "15.3 13.3 11.9": ["favicons"], "5.0 -4.4 3.1": ["pedestrianising"], "4.9 5.0 4.6": ["ordainment"], "12.3 11.6 8.5": ["gridlines"], "7.8 7.9 32.2": ["outports"], "10.0 10.6 5.3": ["straplines"], "-4.2 1.4 -1.7": ["antitussive"], "0.8 1.3 10.7": ["entweder"], "11.6 -3.3 19.3": ["billies"], "5.6 -1.1 13.9": ["pintucks"], "4.5 5.3 9.2": ["subregionals"], "-1.5 12.9 8.0": ["metacognitive"], "-4.0 12.5 5.1": ["hypovolemia"], "3.8 16.8 36.7": ["watermilfoil"], "1.8 14.2 12.5": ["bifenthrin"], "13.9 9.8 6.2": ["lockset"], "-0.3 10.2 8.5": ["embrittlement"], "1.4 3.2 7.8": ["drived"], "23.5 7.3 15.7": ["facefirst"], "7.3 -5.7 0.7": ["lsat"], "6.4 -3.8 8.0": ["minimarts"], "13.5 19.9 16.7": ["nutz"], "5.2 0.5 5.0": ["eyefortransport"], "-7.9 1.7 12.2": ["consultor"], "12.0 11.0 8.1": ["venezuela"], "8.1 -2.0 18.5": ["sak"], "-1.9 11.4 7.6": ["cyclins"], "12.4 7.8 15.2": ["fitba"], "6.1 6.1 4.1": ["itemising"], "7.7 1.9 5.7": ["bahn"], "3.3 13.5 14.0": ["dekh"], "15.1 9.2 20.3": ["seymour"], "16.0 1.9 3.6": ["privitisation"], "8.1 5.9 1.7": ["bietet"], "8.3 8.7 15.1": ["metalcasting"], "3.1 1.1 -1.0": ["processable"], "-8.7 -0.5 -0.5": ["ervices"], "-3.2 20.2 2.4": ["conciliated"], "16.5 12.0 14.0": ["jolliness"], "8.9 3.2 16.8": ["bula"], "0.0 -4.6 5.3": ["nge"], "10.3 14.9 5.6": ["evitable"], "4.6 14.1 8.2": ["hypothesising"], "19.3 2.9 6.3": ["cyclinder"], "5.2 4.0 31.1": ["sportboat"], "-1.9 23.9 3.8": ["consituents"], "7.5 4.8 15.1": ["wy"], "2.3 -2.7 3.6": ["methylene"], "10.2 3.1 10.2": ["inkings"], "2.1 11.5 9.4": ["bunkroom"], "-4.3 9.2 8.8": ["intercommunity"], "9.2 15.4 9.4": ["showboater"], "14.3 6.9 15.5": ["neary"], "3.4 6.6 1.4": ["trova"], "18.5 16.9 4.6": ["stokers"], "7.7 4.4 16.1": ["shimming"], "2.5 21.4 3.9": ["multisensor"], "19.1 1.2 13.4": ["shrinkwrapped"], "2.6 4.4 -0.5": ["restaffed"], "6.8 28.5 5.1": ["complicitous"], "2.6 15.0 17.1": ["xsl"], "14.9 14.1 30.2": ["japonicus"], "-2.7 6.5 4.0": ["longplayer"], "2.1 -1.0 0.1": ["gynae"], "12.8 11.0 10.3": ["ropeline"], "3.1 8.5 3.7": ["germicide"], "13.1 9.1 43.0": ["sportfishermen"], "10.5 12.4 12.0": ["bullbar"], "5.1 11.0 8.5": ["transmissivity"], "14.2 -0.8 7.7": ["gle"], "4.2 9.8 5.5": ["convos"], "8.6 5.8 12.2": ["shirley"], "2.7 0.1 -6.4": ["tonabersat"], "-0.1 0.6 8.6": ["bons"], "13.7 16.7 2.7": ["flagellating"], "9.7 8.0 6.9": ["metabolising"], "4.0 9.0 6.0": ["excells"], "3.7 17.4 2.1": ["infuriation"], "22.7 10.4 15.5": ["flogger"], "12.5 13.3 3.5": ["unignorable"], "1.0 11.3 11.9": ["khud"], "1.8 10.7 -0.4": ["endorsment"], "2.4 10.2 9.6": ["gutsed"], "3.5 -0.0 13.4": ["psd"], "4.9 7.5 11.9": ["danielle"], "10.0 11.4 11.7": ["gentrifiers"], "8.8 4.9 5.3": ["bioscientist"], "7.3 -3.2 37.0": ["balsamico"], "0.4 4.1 4.4": ["geostatistics"], "14.1 12.1 10.8": ["twittersphere"], "7.8 6.6 21.9": ["premolars"], "6.5 4.9 13.1": ["leasees"], "17.6 -1.4 6.6": ["ummed"], "6.8 6.2 6.0": ["decended"], "3.3 5.4 14.2": ["tanka"], "-5.2 2.0 6.7": ["rocuronium"], "23.9 8.7 5.7": ["leccy"], "7.9 0.4 -0.3": ["benzophenone"], "-3.0 0.2 10.0": ["wardship"], "-6.8 7.3 9.0": ["benefi"], "-1.0 0.7 -2.9": ["pesident"], "2.0 7.5 0.0": ["aftermatch"], "9.3 -0.6 13.6": ["refinisher"], "6.7 7.9 17.0": ["beel"], "5.7 6.7 8.3": ["maskandi"], "8.4 -0.8 10.9": ["volumetrics"], "6.4 3.5 1.9": ["denationalisation"], "6.7 16.4 11.7": ["geosmin"], "7.3 4.6 20.6": ["suezmax"], "11.8 6.5 14.8": ["suzuki"], "9.4 8.5 5.4": ["medecine"], "-5.6 6.4 4.6": ["disfavoring"], "18.6 0.2 28.1": ["nopal"], "-10.0 -3.0 3.3": ["psychoeducational"], "14.7 10.8 -0.2": ["alreay"], "7.1 7.1 11.9": ["kaffeeklatsch"], "6.1 12.0 4.0": ["accelerative"], "17.7 6.4 14.7": ["miasmic"], "0.2 10.2 8.4": ["phosphorylates"], "11.2 2.2 12.3": ["barytes"], "8.8 2.3 13.9": ["screwless"], "15.5 15.5 20.0": ["noooooo"], "-2.9 4.8 -1.6": ["coleader"], "12.4 9.6 17.6": ["didge"], "-4.6 7.1 6.2": ["micromolar"], "-0.7 17.1 14.1": ["nihon"], "10.0 1.1 9.1": ["lettershop"], "7.9 13.0 4.1": ["humourously"], "3.0 8.8 7.8": ["vemurafenib"], "13.1 17.2 13.1": ["moneyless"], "-3.9 18.8 -3.6": ["intereference"], "2.3 14.2 4.5": ["succed"], "4.6 10.7 15.6": ["yinz"], "17.5 7.4 7.6": ["lans"], "1.9 9.6 8.7": ["patricia"], "9.7 21.4 4.8": ["elitest"], "3.8 19.9 5.5": ["rebarbative"], "12.7 26.5 12.2": ["botmaster"], "22.5 12.3 14.7": ["dunghill"], "22.3 0.9 8.5": ["banco"], "17.7 17.3 15.1": ["chrissake"], "4.4 2.9 30.7": ["nestings"], "0.1 2.2 11.1": ["leukodystrophy"], "9.9 -4.7 1.7": ["gasworld"], "15.0 5.0 0.1": ["servcies"], "4.0 16.4 11.3": ["restrengthening"], "-7.1 -0.3 2.7": ["saif"], "3.0 9.8 9.9": ["noncompetes"], "5.3 10.7 20.6": ["bubby"], "9.8 0.4 7.6": ["unreels"], "2.3 5.4 3.7": ["multistream"], "12.9 13.3 18.4": ["pedro"], "6.7 15.5 16.9": ["unkosher"], "19.8 11.1 27.2": ["drongos"], "-5.0 19.6 0.7": ["kapo"], "2.8 11.0 7.5": ["biwi"], "12.0 10.9 15.3": ["oglers"], "15.7 8.9 12.5": ["duded"], "10.2 2.5 14.4": ["rodding"], "7.0 -1.1 19.8": ["broadcloth"], "4.4 11.6 12.6": ["amygdalas"], "10.2 25.1 14.8": ["varyingly"], "16.9 14.5 18.8": ["whooo"], "2.7 35.3 8.2": ["humint"], "-2.0 7.0 0.4": ["thrombophlebitis"], "13.4 6.1 15.4": ["decoratives"], "2.8 11.2 9.9": ["overtaxes"], "16.9 17.8 5.1": ["reimagination"], "-3.2 8.5 2.7": ["filmers"], "15.0 9.5 -1.8": ["interent"], "11.0 7.4 11.0": ["transverses"], "2.0 8.6 22.6": ["lanzones"], "3.8 17.1 6.1": ["killled"], "-2.9 10.3 10.7": ["beutiful"], "4.6 2.9 29.2": ["cashewnuts"], "16.9 8.6 7.8": ["yucked"], "2.9 11.8 4.1": ["eotaxin"], "-0.9 11.4 11.8": ["reclosed"], "-8.3 11.0 -3.7": ["theologist"], "-1.0 18.3 4.6": ["contemnor"], "22.3 16.6 3.7": ["untethering"], "-1.8 7.6 4.9": ["langars"], "26.4 11.4 15.9": ["clodhoppers"], "2.5 8.8 9.9": ["demander"], "6.1 13.9 20.1": ["courtin"], "11.1 11.0 21.4": ["leetle"], "12.5 18.4 2.3": ["waterbombers"], "-1.6 3.3 2.9": ["subcircuit"], "5.5 15.9 14.4": ["starcraft"], "1.3 14.8 6.4": ["omar"], "3.8 11.3 10.9": ["bha"], "-4.0 10.4 17.0": ["climatologically"], "6.7 15.0 8.6": ["diplo"], "-4.8 0.3 -0.4": ["antifolate"], "17.2 21.2 9.9": ["tunnelers"], "2.0 8.3 9.9": ["poolers"], "10.4 28.9 15.4": ["forcers"], "1.7 0.1 2.1": ["prevous"], "6.2 -2.0 0.8": ["eightyear"], "-0.1 0.7 5.2": ["eral"], "16.3 11.9 12.8": ["saddo"], "10.2 21.0 21.9": ["snobbism"], "8.3 12.4 10.7": ["toweringly"], "9.3 9.1 24.7": ["pyrosomes"], "10.8 23.6 27.3": ["phytophthora"], "14.8 1.4 16.2": ["tableful"], "1.0 13.7 25.3": ["homeporting"], "-8.3 3.0 3.5": ["tof"], "-1.4 19.3 15.9": ["phagosome"], "12.6 9.0 23.4": ["provenances"], "4.6 13.8 3.3": ["unfastening"], "2.5 0.3 18.4": ["luk"], "12.8 14.8 1.4": ["stigmatic"], "15.7 6.9 22.9": ["galahs"], "4.7 12.8 14.2": ["xeriscaped"], "22.5 3.6 19.0": ["horsies"], "1.0 5.3 18.5": ["nonrevenue"], "-1.2 1.8 6.4": ["reccommended"], "9.9 22.5 16.3": ["infinities"], "4.2 8.9 6.2": ["datastores"], "2.6 26.7 9.1": ["obscurantists"], "3.9 13.9 10.4": ["crosslinks"], "10.7 17.7 13.2": ["dawdlers"], "14.7 6.9 5.3": ["ropeways"], "1.6 -8.1 15.3": ["fourday"], "6.9 -4.6 8.6": ["uhr"], "17.4 14.7 18.3": ["urgh"], "9.9 19.4 12.2": ["virago"], "-0.9 10.0 1.3": ["miltefosine"], "8.6 10.0 13.7": ["prissiness"], "12.1 11.0 31.2": ["flytraps"], "7.4 9.2 15.7": ["spalike"], "3.5 24.2 7.2": ["intangibility"], "12.0 17.5 15.7": ["homogeny"], "14.4 9.7 19.1": ["bilbies"], "6.8 4.6 11.7": ["proprietorships"], "17.1 16.4 15.0": ["buddhas"], "6.1 12.8 22.7": ["chirpiness"], "7.5 21.8 6.8": ["bestir"], "9.9 1.2 40.9": ["dipnet"], "0.5 2.6 11.7": ["manalo"], "8.6 0.4 21.1": ["seng"], "17.1 18.3 14.4": ["bounders"], "3.9 12.7 8.3": ["syphillis"], "-0.4 9.6 5.9": ["immunodeficient"], "6.3 12.3 16.1": ["categorisations"], "18.3 14.5 2.5": ["moscow"], "9.5 16.2 21.3": ["foresail"], "7.5 14.1 27.7": ["sandpapery"], "-0.1 16.5 1.3": ["reprecussions"], "1.7 16.0 4.6": ["transpartisan"], "5.8 10.6 5.1": ["cemetry"], "15.0 1.2 9.5": ["sportsfield"], "10.4 6.9 15.1": ["featherbeds", "glitteringly"], "17.5 10.3 30.7": ["crostata"], "3.2 2.2 6.4": ["rougly"], "14.6 8.0 12.9": ["cuddlers"], "-15.4 2.0 9.4": ["unexhausted"], "7.9 20.7 12.0": ["outcastes"], "-6.0 -2.2 5.5": ["refundability"], "-2.0 23.7 11.0": ["firster"], "9.2 10.3 13.6": ["toneless"], "13.7 22.8 24.8": ["duppy"], "2.5 21.8 2.2": ["hierarchic"], "22.7 6.5 28.5": ["piggie"], "-2.0 1.6 4.1": ["mre"], "22.1 7.9 5.3": ["sandtrap"], "16.8 11.1 3.3": ["profitting"], "-0.1 7.0 10.8": ["metavolcanics"], "1.0 11.0 8.4": ["prolixity"], "3.5 11.6 13.2": ["rhymers"], "-1.4 7.9 3.0": ["distrct"], "11.7 22.1 11.9": ["zelda"], "1.4 6.8 10.1": ["mezuzot"], "12.8 4.5 29.3": ["supa"], "2.1 -0.2 -0.7": ["acousticians"], "13.2 8.1 6.0": ["underproductive"], "3.1 8.6 9.9": ["lamasery"], "13.1 5.5 6.8": ["majap"], "0.7 1.0 17.5": ["absinthes"], "-7.9 2.8 8.3": ["bupe"], "-1.4 -3.5 2.4": ["reanalysed"], "14.8 13.0 10.9": ["achromatic"], "3.6 3.4 9.8": ["forclosures"], "-2.0 19.3 6.9": ["antichoice"], "14.4 3.4 17.0": ["snowpark"], "9.8 16.6 4.6": ["opprobrious"], "4.5 -1.2 38.4": ["soppressata"], "-4.5 10.2 3.5": ["sensitises"], "-10.0 10.9 -0.1": ["ustaz"], "5.9 13.2 14.4": ["knacks"], "10.6 12.8 11.5": ["bernie"], "9.4 6.4 9.9": ["southsiders"], "6.0 16.4 29.8": ["canid"], "10.1 2.1 5.3": ["orld"], "10.2 3.2 3.9": ["waar"], "1.8 9.7 4.1": ["trainmaster"], "-1.6 10.6 17.0": ["rangatira"], "8.0 5.4 14.7": ["pob"], "6.9 1.5 9.2": ["reinspecting"], "2.2 3.4 16.9": ["oenological"], "-3.4 -5.9 9.4": ["unallotted"], "2.5 0.5 15.6": ["tinning"], "12.9 7.8 13.0": ["quelle"], "0.5 4.9 15.3": ["poomsae"], "10.8 6.1 26.7": ["hawaiian"], "15.8 3.1 12.6": ["glazer"], "8.5 20.0 12.7": ["carpers"], "8.0 -2.7 6.3": ["refractometers"], "10.9 0.4 9.9": ["stree"], "4.8 13.3 4.0": ["ttl"], "-4.6 9.7 4.6": ["benefice"], "1.6 13.0 19.3": ["nami"], "3.1 10.4 11.7": ["yond"], "-6.3 -0.6 2.7": ["cosigners"], "18.7 5.2 25.5": ["beefburgers"], "-3.1 -1.0 -2.3": ["folowed"], "12.2 13.2 11.8": ["annointing"], "14.0 1.4 43.4": ["ebi"], "20.6 7.0 25.2": ["leatherworking"], "4.5 12.3 6.5": ["baryon"], "10.9 5.2 3.2": ["syste"], "3.8 8.7 13.5": ["kitesurf"], "-0.4 10.3 -0.1": ["workingwomen"], "2.2 10.2 -2.7": ["xxix"], "2.4 10.6 -4.8": ["icc"], "-6.1 11.2 0.2": ["systemizing"], "5.2 8.6 10.0": ["kickings"], "12.0 9.8 4.2": ["geothermic"], "-4.1 8.1 -3.2": ["deponents"], "5.6 16.1 3.4": ["boded"], "7.3 9.7 -3.7": ["framegrab"], "5.0 10.8 -2.5": ["overwrote"], "13.6 20.9 33.4": ["diamondbacks"], "13.6 3.5 1.0": ["phonographic"], "13.9 23.5 21.1": ["cootie"], "6.0 16.7 1.3": ["comporting"], "11.2 19.0 13.0": ["khukri"], "6.1 -0.3 7.4": ["multidisc"], "-6.3 5.0 -2.4": ["staement"], "-0.1 7.7 12.6": ["weightbearing"], "9.7 19.4 12.2": ["unrealism"], "9.8 12.7 14.8": ["succa"], "7.4 8.6 23.2": ["soilless"], "7.5 22.1 6.2": ["europhile"], "16.7 17.4 3.6": ["banalization"], "8.4 8.2 -0.9": ["renewably"], "11.1 20.5 23.1": ["yerself"], "5.3 14.8 12.7": ["reassort"], "-6.0 12.7 -0.6": ["afterwhich"], "5.8 4.9 21.9": ["tikkas"], "-4.5 6.8 9.4": ["cantos"], "-1.9 11.1 8.5": ["uplist"], "5.8 9.6 14.3": ["ploughmen"], "-5.2 2.9 8.1": ["prepartion"], "5.8 15.0 13.2": ["dispersement"], "3.4 -2.9 16.9": ["bles"], "18.3 -4.0 1.2": ["parternship"], "3.9 2.9 12.5": ["trunklines"], "1.9 15.6 14.0": ["neuroncologist"], "8.7 9.0 3.7": ["hosanna"], "12.4 8.2 11.6": ["dismantler"], "4.5 14.5 -2.8": ["lenghts"], "18.7 4.4 11.6": ["larked"], "7.2 6.7 5.3": ["mudrooms"], "-7.7 7.9 6.6": ["presbyters"], "1.2 1.8 46.6": ["gillnetter"], "1.4 8.5 17.2": ["khas"], "3.3 16.2 8.8": ["hamhanded"], "12.6 -1.4 15.8": ["keeners"], "8.0 20.3 8.6": ["electioneer"], "11.0 10.6 26.4": ["luging"], "11.6 10.3 -1.2": ["gamigo"], "24.3 -0.7 6.1": ["bedecking"], "8.5 24.0 4.5": ["triune"], "5.3 3.9 10.2": ["jotters"], "-4.8 17.1 8.6": ["appauling"], "17.6 -1.7 -10.2": ["zavvi"], "10.2 -3.9 17.5": ["tassle"], "9.0 10.4 13.6": ["tappable"], "2.8 17.8 10.1": ["overcomplicating"], "-1.8 0.8 6.7": ["payscales"], "15.8 -1.5 4.0": ["pubcasters"], "1.8 10.1 13.1": ["ovule"], "-2.0 19.7 6.3": ["counterposed"], "6.6 26.0 7.3": ["sowers"], "3.2 14.1 16.1": ["liya"], "19.9 7.8 -1.3": ["mislaying"], "24.2 10.1 20.4": ["windchimes"], "16.1 4.0 11.4": ["wieldy"], "6.5 2.6 1.2": ["postdoctorate"], "10.5 3.4 5.3": ["presorting"], "12.8 -1.9 9.8": ["primps"], "-3.4 17.0 8.7": ["evers"], "17.6 0.6 21.5": ["fuscia"], "6.6 14.8 13.1": ["overachieves"], "13.1 12.9 13.8": ["cheapskateblog"], "6.0 9.5 21.8": ["applejack"], "17.1 9.7 24.2": ["rockwork"], "16.0 8.4 21.1": ["tootsie"], "11.8 14.5 5.9": ["hoodwinks"], "2.8 9.5 14.7": ["argillites"], "-1.7 16.4 -0.1": ["opprtunity"], "5.0 -1.4 10.7": ["iffier"], "19.0 0.0 15.5": ["chr"], "4.2 21.4 7.4": ["withouth"], "21.5 5.2 7.7": ["milions"], "2.2 4.2 8.5": ["thymol"], "14.1 7.7 -4.2": ["abandonned"], "11.6 6.0 20.0": ["cashpot"], "-2.6 39.6 14.0": ["debuffs"], "5.0 2.3 12.2": ["seul"], "6.1 7.9 26.0": ["crustier"], "5.3 12.1 -3.4": ["phon"], "3.2 11.0 9.7": ["videograph", "behaviourial"], "-2.2 17.8 8.8": ["disarticulation"], "17.0 12.9 16.5": ["burpees"], "13.1 12.7 13.7": ["aureole"], "5.4 16.7 18.4": ["yakyu"], "-2.2 8.8 4.5": ["exicted"], "4.4 16.1 5.8": ["posesses"], "-3.8 0.3 10.8": ["reliver"], "-1.3 16.4 0.9": ["juridically"], "12.2 7.0 10.6": ["hipsterdom"], "0.4 20.7 4.3": ["historiographical"], "11.9 11.5 17.5": ["remeasure"], "15.0 11.6 10.4": ["nimblest"], "3.2 -3.3 5.1": ["mising"], "0.3 -3.0 4.0": ["hymnody"], "25.2 6.5 14.7": ["lickable"], "8.1 20.1 2.3": ["compund"], "16.2 -0.3 10.6": ["sideburned"], "16.0 7.6 7.2": ["scratchproof"], "-2.6 -3.5 15.9": ["castorseed"], "4.7 1.4 3.4": ["floorstanding"], "2.6 5.3 2.0": ["criminalistics"], "10.8 27.3 7.9": ["hiders"], "9.2 5.6 26.6": ["precook"], "10.2 23.0 2.9": ["ufologists"], "-3.5 6.2 -1.2": ["homoeopath"], "2.1 -8.8 3.3": ["outlayed"], "4.6 13.7 10.9": ["bednet"], "-7.1 9.1 2.9": ["vasoconstrictor"], "11.8 1.7 6.7": ["homebrews"], "16.8 0.8 16.3": ["snipper"], "5.3 8.1 7.9": ["recolored"], "11.3 11.6 14.4": ["dognapper"], "1.0 9.8 12.6": ["acellular"], "-8.1 -0.5 7.7": ["nonaccredited"], "19.2 2.4 13.0": ["bicyle"], "7.1 5.2 5.8": ["ffwd"], "-0.6 7.3 10.2": ["ordinace"], "6.6 3.5 6.7": ["onging"], "10.7 10.0 13.3": ["prototypically"], "-0.8 3.7 10.3": ["tean"], "5.4 15.1 1.0": ["refueller"], "7.0 23.8 9.5": ["monarchism"], "14.6 8.8 6.6": ["censorware"], "10.6 4.6 22.0": ["unbagged"], "15.7 41.1 10.2": ["panzer"], "3.8 5.8 15.5": ["crutching"], "5.4 1.6 8.9": ["ricks"], "8.8 2.1 11.5": ["screencasting"], "6.3 8.3 19.7": ["kiri"], "4.9 10.8 6.8": ["gentlemanliness"], "12.3 9.5 22.4": ["mummifying"], "-4.2 9.9 8.9": ["factures"], "1.2 3.0 -2.7": ["structurer"], "15.8 6.6 5.7": ["maharishi"], "0.1 4.2 1.2": ["advanatge"], "7.7 22.9 0.9": ["islamophobia"], "4.4 11.9 18.7": ["asthenosphere"], "0.3 0.0 -6.0": ["organsiation"], "7.0 11.0 11.3": ["scratchiness"], "-2.7 7.3 0.3": ["airlinks"], "-10.4 4.3 -1.7": ["reinterviewing"], "9.0 0.8 22.0": ["lusterless"], "-3.5 9.7 6.0": ["needlesticks"], "9.9 15.9 29.4": ["fieldstones"], "1.2 19.7 -8.5": ["protrayed"], "3.9 20.1 9.8": ["semitic"], "12.8 9.1 7.4": ["overdependent"], "17.8 13.3 21.6": ["tushy"], "3.0 10.1 16.4": ["methomyl"], "8.9 5.9 11.4": ["snappiness"], "8.7 0.2 3.3": ["printnet"], "17.9 5.6 14.8": ["tenatively"], "8.6 5.9 13.5": ["seri"], "3.0 26.1 5.5": ["weltanschauung"], "17.8 -5.9 8.0": ["exiderdome"], "1.8 8.9 10.8": ["carolyn"], "2.7 1.0 -5.0": ["revealled"], "-0.8 -0.7 6.5": ["sevent"], "13.2 10.5 19.0": ["vomitous"], "5.3 0.6 19.2": ["tsung"], "10.1 14.1 6.4": ["multibranding"], "28.2 11.7 18.1": ["scrabbles"], "4.0 7.4 9.6": ["adb"], "18.9 18.1 11.5": ["genii"], "5.6 26.3 2.7": ["delusory"], "-2.5 9.8 14.4": ["dered"], "-0.3 12.0 13.9": ["rgb"], "0.1 1.7 4.8": ["matchmine"], "8.9 3.5 11.1": ["spaceflyers"], "6.4 -1.4 16.1": ["shortcovering"], "4.6 7.6 10.2": ["theh"], "8.7 12.1 21.2": ["retying"], "2.6 -4.9 3.3": ["erson"], "-5.9 0.3 10.7": ["terest"], "4.8 2.2 2.3": ["bishoprics"], "3.1 10.3 -0.7": ["ammend"], "16.7 6.6 -1.2": ["producting"], "-8.4 6.3 0.8": ["posttest"], "13.4 11.3 19.6": ["chopsocky"], "-0.1 14.1 7.8": ["thoses"], "10.2 4.2 9.9": ["throu"], "0.7 11.4 14.3": ["enucleation"], "20.5 6.3 -3.8": ["frim"], "6.5 10.1 25.7": ["dryish"], "11.7 12.5 -3.2": ["sensored"], "4.4 12.6 14.3": ["androstenone"], "-4.3 15.1 -5.3": ["elaborative"], "-0.2 7.7 10.8": ["ceftazidime"], "5.5 12.0 3.4": ["verson"], "0.7 5.4 6.3": ["gazettement"], "5.0 24.3 3.2": ["unislamic"], "16.7 2.4 42.6": ["masago"], "11.7 13.2 10.0": ["superbitch"], "1.9 1.1 4.6": ["gravelling"], "17.5 18.5 28.0": ["spathe"], "4.7 15.6 8.4": ["afterlives"], "13.5 19.9 12.1": ["autarkic"], "13.9 11.8 31.3": ["fingerlike"], "-1.8 -6.3 5.0": ["outpasses"], "4.7 12.8 10.0": ["unassessed"], "-1.9 23.0 13.9": ["flashforwards"], "11.9 6.1 3.0": ["trainman"], "1.1 25.8 1.1": ["regionalists"], "17.8 -2.3 5.0": ["glueless"], "-4.4 5.6 2.3": ["asparaginase"], "6.3 7.9 11.4": ["irradiators"], "12.7 18.7 30.5": ["spiderwort"], "0.5 5.8 -0.9": ["reallife"], "6.9 9.5 15.8": ["ectoderm"], "7.6 6.0 7.8": ["mebendazole"], "15.7 -5.9 8.8": ["omphalocele"], "7.1 18.8 16.6": ["ironists"], "7.2 0.3 30.4": ["merguez"], "12.4 5.6 7.9": ["cci"], "11.5 15.6 20.1": ["recolonized"], "1.9 14.7 -6.2": ["possesed"], "0.6 11.7 4.2": ["anil"], "23.1 5.3 13.3": ["forestries"], "12.6 0.9 12.7": ["ballpoints"], "2.6 -1.0 6.0": ["adipogenesis"], "-0.1 6.3 5.3": ["annull"], "4.3 3.3 10.2": ["heon"], "16.4 24.3 12.4": ["dissappear"], "8.0 21.6 14.2": ["blatancy"], "6.2 8.6 52.8": ["opihi"], "15.3 8.0 22.6": ["purply"], "9.5 7.5 3.3": ["reskill"], "-3.0 4.9 1.7": ["warrents"], "5.4 18.4 10.4": ["upshifting"], "13.6 20.7 13.2": ["impalpable"], "3.9 5.8 8.0": ["passcard"], "6.3 17.4 8.5": ["breakover"], "3.2 3.8 8.4": ["athree"], "14.5 19.5 10.0": ["incautiously"], "9.5 7.7 11.6": ["branders"], "13.1 7.8 10.2": ["juego"], "-0.2 5.1 4.6": ["somatization"], "6.0 11.1 8.7": ["behenji"], "6.7 -2.7 3.4": ["hollywooddivas"], "8.8 1.2 6.9": ["emc"], "7.6 1.8 8.6": ["surburbs"], "10.2 10.3 -2.6": ["defectively"], "4.6 5.1 19.3": ["stockbuilding"], "5.7 9.3 8.8": ["mutal"], "15.2 22.7 2.2": ["defiler"], "-3.3 12.7 2.3": ["hajib"], "3.2 10.6 1.3": ["comparo"], "17.3 -0.5 25.1": ["calla"], "0.3 20.5 12.1": ["northing"], "2.9 3.4 2.6": ["kilomtres"], "-0.7 9.0 9.7": ["hallmates"], "7.9 12.8 10.6": ["anticlimactically"], "-4.8 -4.0 -8.0": ["ghostwrote"], "9.7 3.2 9.3": ["moonbuggy"], "10.0 8.5 2.1": ["ginnel"], "-2.2 20.7 9.6": ["communicability"], "5.8 1.0 5.8": ["gowning"], "12.8 11.1 3.3": ["piezoelectricity"], "6.6 8.9 9.8": ["offerers"], "3.0 4.6 12.5": ["saccharides"], "11.6 13.4 23.6": ["banksia"], "13.0 11.7 16.2": ["kernal"], "6.3 4.7 17.9": ["sayang"], "17.6 0.3 17.0": ["charabanc"], "18.0 27.6 14.8": ["superorganism"], "7.6 7.4 28.6": ["mushroomy"], "-4.7 16.3 5.0": ["prayerfulness"], "2.1 10.6 5.8": ["interactional"], "3.4 20.2 11.3": ["disproof"], "10.3 1.7 9.3": ["gest"], "-3.3 13.9 4.9": ["whoare"], "10.4 8.1 25.4": ["bioresources"], "9.4 4.5 30.4": ["maitake"], "3.2 15.3 15.5": ["divisibility"], "5.9 8.8 8.0": ["monolinguals"], "9.5 14.9 11.2": ["parapsychologists"], "-1.6 10.7 4.7": ["khusra"], "-4.7 21.1 15.5": ["clostridia"], "1.0 15.9 0.4": ["depoliticisation"], "9.8 0.3 -0.4": ["produit"], "4.2 7.2 13.1": ["repaves"], "5.5 21.9 16.7": ["indiginous"], "6.7 7.5 4.9": ["notational"], "0.7 30.1 5.0": ["remilitarization"], "5.6 20.3 5.8": ["mediocres"], "8.1 25.3 11.1": ["nonmagical"], "14.3 4.2 10.3": ["suppy"], "18.0 10.2 13.0": ["barclays"], "13.0 14.9 6.9": ["madding"], "18.1 12.4 20.6": ["coochie"], "2.6 14.4 6.7": ["pathologize"], "2.1 12.4 7.6": ["endian"], "6.8 4.6 1.0": ["demostrate"], "3.3 11.2 17.0": ["gae"], "2.4 10.8 4.6": ["frought"], "11.1 4.0 7.5": ["philips"], "-3.4 14.1 3.1": ["precommit"], "1.0 10.2 10.4": ["gunbelt"], "9.8 -4.4 2.3": ["highlighed"], "11.4 4.4 11.6": ["readymades"], "0.7 11.0 15.1": ["dorsum"], "1.9 13.7 8.3": ["forthing"], "-8.3 16.4 -0.1": ["unifocal"], "9.5 0.4 33.1": ["fishos"], "9.1 2.3 4.0": ["utilties"], "15.0 14.8 6.7": ["phonebox"], "2.7 -1.3 -8.9": ["sprl"], "0.6 -2.4 8.3": ["kbyte"], "2.7 19.8 11.5": ["panick"], "-3.6 8.3 10.9": ["microbiologically"], "13.3 11.2 6.8": ["bludging"], "4.4 14.6 10.3": ["autoerotic"], "4.3 -0.6 17.8": ["competitons"], "6.0 7.3 8.3": ["thresholding"], "14.5 20.5 19.0": ["echolocate"], "6.9 7.3 9.4": ["clioquinol"], "2.7 10.1 22.4": ["cottonseeds"], "4.3 1.3 1.5": ["ringroad"], "5.0 7.3 13.7": ["transcriptomics"], "15.7 21.7 19.3": ["woooo"], "8.8 4.2 5.0": ["nonsanctioned"], "9.6 6.0 22.4": ["downlist"], "0.6 16.5 4.5": ["continuums"], "20.3 20.3 0.7": ["highpowered"], "7.1 2.0 8.7": ["twosies"], "2.0 20.4 0.5": ["safing"], "7.7 19.5 1.5": ["propogated"], "9.1 17.3 10.4": ["maddens"], "11.1 4.6 13.6": ["jardin"], "6.2 1.8 15.0": ["iawn"], "1.3 6.2 13.1": ["yuri"], "11.8 8.3 2.9": ["amero"], "10.5 11.2 21.3": ["takraw"], "5.5 11.2 11.6": ["presymptomatic"], "4.6 -1.2 8.1": ["embossers"], "17.2 8.0 13.2": ["overscaled"], "12.1 7.6 8.6": ["liabilty"], "14.5 8.5 6.7": ["nonapproved"], "24.2 20.2 10.9": ["souless"], "2.2 -12.5 5.4": ["chiropodists"], "-2.5 2.3 14.2": ["foruth"], "-6.1 16.6 4.2": ["justifiability"], "-6.2 9.9 3.0": ["aminoglycoside"], "2.7 5.6 3.4": ["sexuals"], "3.3 -3.8 -3.9": ["whichwill"], "2.4 9.4 13.9": ["roarin"], "-2.4 -7.3 4.7": ["lene"], "11.0 -1.1 13.9": ["adoptathon"], "7.9 14.3 11.9": ["snorefest"], "8.2 15.0 9.5": ["brakeless"], "7.0 11.3 12.5": ["easeful"], "1.2 8.5 1.9": ["immensly"], "6.5 8.9 21.6": ["suki"], "3.0 4.4 10.7": ["rehydrates"], "9.3 6.6 5.2": ["chlorinators"], "-5.7 19.9 3.8": ["isthat"], "20.8 -0.7 12.9": ["eum"], "10.1 2.5 14.8": ["seafreight"], "27.9 8.2 1.4": ["thirdlargest"], "14.0 1.8 13.9": ["jit"], "-2.5 5.4 8.7": ["esperanza"], "14.7 -5.2 -1.3": ["markt"], "4.9 10.4 11.0": ["plastid"], "3.0 13.6 13.3": ["boyracers"], "-4.7 9.4 2.3": ["accountablity"], "8.8 3.7 6.9": ["neuritis"], "9.5 27.4 9.3": ["foredoomed"], "2.2 4.8 6.3": ["dealnews"], "2.0 19.3 7.9": ["dispossesses"], "-0.1 8.7 11.5": ["coalbeds"], "1.4 6.7 1.6": ["equivelant"], "1.7 7.7 14.2": ["wondeful"], "14.0 14.2 7.3": ["tranformation"], "3.7 7.5 35.3": ["whitebaiting"], "-4.2 8.9 17.5": ["aerification"], "7.0 9.0 12.1": ["eaglefly"], "5.7 13.1 13.6": ["tinea"], "-0.8 8.4 10.0": ["munshi"], "10.4 12.8 28.6": ["petioles"], "4.7 -1.2 2.1": ["coldset"], "1.5 8.2 0.0": ["femicides"], "-7.5 5.0 0.1": ["unadjudicated"], "5.8 -2.7 6.3": ["cinq"], "6.5 13.2 25.7": ["loblolly"], "16.6 14.5 16.2": ["trollish"], "0.3 10.7 2.6": ["ammends"], "-3.3 5.4 13.1": ["metaphase"], "-0.0 20.8 0.5": ["politcs"], "16.5 10.0 17.6": ["toroid"], "8.8 23.5 12.1": ["murkily"], "7.1 4.4 9.3": ["guis"], "-3.4 8.4 6.6": ["breathwork"], "9.4 20.7 13.5": ["benitez"], "16.6 6.1 6.7": ["patchworked"], "-0.1 14.9 12.7": ["arsenite"], "-0.2 4.0 4.5": ["orthotist"], "8.4 27.5 16.3": ["reinfect"], "19.9 10.5 12.8": ["grotesquery"], "1.7 2.6 15.5": ["mtb"], "7.7 11.9 4.1": ["unerotic"], "-6.1 6.1 6.0": ["cumann"], "5.7 6.9 8.7": ["hairbreadth"], "3.8 27.1 -2.2": ["stouthearted"], "2.9 6.5 8.5": ["scooty"], "13.0 15.1 31.5": ["redwings"], "14.7 9.7 15.9": ["kickline"], "6.6 12.1 8.3": ["driveby"], "17.1 -2.4 9.7": ["oktober"], "1.2 7.4 2.3": ["speakout"], "-0.7 9.2 10.6": ["conguero"], "-3.6 16.4 -2.1": ["sitaution"], "4.3 8.5 4.8": ["nombre"], "5.2 9.2 13.7": ["provitamin"], "9.1 20.0 12.6": ["usurer"], "5.2 5.8 9.4": ["studbook"], "13.7 9.9 15.3": ["whoah"], "13.2 2.0 3.8": ["microsensor"], "19.3 12.3 23.8": ["pothos"], "18.3 -0.4 -3.8": ["yearsago"], "8.7 1.0 16.4": ["sav"], "6.2 22.5 20.7": ["solanine"], "9.4 36.8 10.9": ["reinvade"], "12.3 7.7 24.1": ["cao"], "7.8 6.9 30.0": ["supersweet"], "8.1 5.6 11.5": ["musharaka"], "5.0 6.1 20.2": ["phuket"], "1.6 -1.0 17.1": ["microsurfacing"], "-1.7 -2.7 -6.4": ["edc"], "-6.2 20.4 0.3": ["tactfulness"], "7.5 26.3 0.8": ["boresight"], "6.0 11.5 6.4": ["dilligent"], "17.2 4.4 14.2": ["shipowning"], "25.7 16.3 31.7": ["clawless"], "10.7 19.3 7.3": ["spiracles"], "-4.6 7.1 7.5": ["clubmen"], "7.2 6.8 0.2": ["palyer"], "9.7 6.6 17.4": ["uy"], "9.3 10.6 11.3": ["undetectably"], "16.3 2.8 28.0": ["cornhusk"], "3.3 -2.9 10.3": ["pasado"], "10.2 7.5 18.5": ["meatworkers"], "11.8 -0.1 10.2": ["billi"], "-0.5 -10.7 3.4": ["receipients"], "5.4 0.4 -0.9": ["rele"], "7.7 35.5 2.1": ["militarys"], "4.9 12.1 15.9": ["hillwalker"], "4.4 9.0 0.4": ["aditional"], "7.0 13.5 16.1": ["malba"], "6.6 10.2 9.4": ["simpy"], "-0.8 9.7 13.4": ["girliness"], "-0.8 15.8 6.2": ["genuflections"], "12.0 20.9 11.7": ["illusionism"], "21.8 6.1 9.8": ["alphorn"], "5.2 17.2 28.1": ["rumrunners"], "7.9 -1.6 6.3": ["commmittee"], "6.2 28.3 2.4": ["figher"], "0.2 -1.8 10.4": ["minitours"], "1.1 10.0 6.6": ["arpeggiator"], "5.4 14.1 15.0": ["unirrigated"], "1.7 22.4 9.8": ["playcall"], "14.3 12.3 23.4": ["mumu"], "-14.3 -4.4 2.5": ["predoctoral"], "2.8 -9.4 7.9": ["nonfaculty"], "9.0 1.6 -5.5": ["theacquisition"], "-0.7 -4.3 -1.4": ["audiocasts"], "5.7 15.6 10.4": ["dipolar"], "-3.6 12.2 7.5": ["noncandidate"], "12.9 3.1 5.2": ["thisis"], "0.3 10.4 0.1": ["bewails"], "8.5 5.6 3.7": ["shrift"], "16.6 10.7 29.2": ["froglets"], "15.6 30.2 8.6": ["exterminates"], "9.9 7.0 19.4": ["poon"], "-2.3 8.7 0.1": ["vicitims"], "16.5 -9.4 2.8": ["recenly"], "1.5 -1.9 2.3": ["registed"], "4.1 1.0 5.2": ["checkweighers"], "29.7 11.5 5.0": ["billionnaire"], "6.5 10.2 18.5": ["foofaraw"], "19.4 19.3 15.4": ["backwoodsman"], "-1.1 19.5 12.2": ["machista"], "11.6 6.1 9.8": ["onder"], "6.8 0.2 16.9": ["silked"], "7.9 11.3 19.7": ["circum"], "15.2 11.1 6.4": ["tody"], "9.6 9.0 7.6": ["meteoritic"], "9.5 19.2 23.2": ["inbreed"], "10.6 11.1 18.2": ["resevoir"], "15.7 20.8 14.7": ["imploringly"], "-0.7 2.6 12.2": ["cytokinin"], "3.5 7.4 15.7": ["letch"], "9.7 6.7 27.3": ["stinkier"], "-6.5 23.4 7.4": ["aggressivity"], "17.0 9.8 11.6": ["dolla"], "18.6 8.1 13.8": ["weeing"], "10.4 32.2 9.2": ["jinns"], "1.4 16.2 9.2": ["overvoting"], "-0.6 10.9 8.3": ["tamilnadu"], "6.0 5.9 15.4": ["chloritic"], "13.4 19.4 0.8": ["deliberatly"], "12.8 9.5 15.4": ["kickflips"], "0.5 -0.8 -4.5": ["ombuds"], "13.9 7.8 9.4": ["loggias"], "7.2 -1.0 9.0": ["upwith"], "0.9 -2.4 0.9": ["korunas"], "0.6 24.5 1.6": ["defeatable"], "1.2 15.2 18.5": ["jangmadang"], "-1.2 -6.8 8.1": ["competions"], "6.8 10.6 9.4": ["deodorizes"], "-4.7 10.8 5.6": ["physcially"], "5.6 7.2 13.9": ["seraphic"], "7.9 13.0 -0.8": ["impermeability"], "6.8 8.6 3.3": ["userid"], "13.1 6.9 24.6": ["bevvies"], "11.1 12.6 16.3": ["weltschmerz"], "3.4 10.3 26.2": ["goi"], "-5.7 -0.3 5.6": ["prac"], "-0.3 13.3 2.8": ["progres"], "11.6 7.3 26.5": ["domestica"], "13.8 8.3 33.7": ["clafouti"], "9.4 11.4 16.8": ["forelocks"], "24.1 20.5 19.4": ["squirter"], "3.0 3.4 11.1": ["tableting"], "11.3 1.9 11.3": ["aires"], "5.8 21.0 3.8": ["fissionable"], "-6.0 12.1 13.1": ["preplant"], "13.3 -1.4 14.5": ["niagara"], "1.0 5.5 51.2": ["rockfishing"], "8.4 8.4 31.0": ["salmonberry"], "36.2 9.9 5.8": ["softwaremaker"], "15.8 23.6 12.9": ["mutator"], "11.5 10.1 10.3": ["willin"], "8.2 1.9 8.0": ["kilometeres"], "4.9 23.6 6.5": ["emnity"], "8.7 4.5 4.3": ["bool"], "-7.0 2.4 7.9": ["angiopoietin"], "0.6 32.4 8.1": ["dittohead"], "3.1 18.9 8.4": ["unsackable"], "15.2 7.4 22.8": ["shashlik"], "11.4 3.1 35.1": ["paleta"], "3.7 14.3 -1.8": ["rallyist"], "22.9 9.2 15.0": ["snuffled"], "-2.7 8.7 8.8": ["droit"], "3.6 6.8 12.9": ["myeon"], "8.1 -0.4 11.9": ["ines"], "3.4 18.7 9.0": ["eviscerations"], "5.9 5.6 7.2": ["landlosers"], "13.7 6.4 9.4": ["descargar"], "4.0 5.3 12.0": ["greenprint"], "10.6 25.5 3.0": ["battledress"], "4.7 16.3 12.9": ["vehciles"], "0.0 6.3 13.4": ["glucophage"], "14.3 -0.1 7.5": ["andon"], "-2.1 6.0 23.3": ["pozzolan"], "-4.8 -5.2 1.7": ["tegaserod"], "-6.8 15.1 5.8": ["teamwise"], "10.0 -2.5 12.9": ["leatherbound"], "-6.8 8.8 10.6": ["interculturalism"], "14.5 15.2 18.8": ["hunny"], "5.8 2.1 15.5": ["poe"], "7.3 -0.5 3.8": ["pmin"], "14.7 25.6 6.9": ["pwnage"], "0.2 7.1 4.8": ["paar"], "-4.6 4.1 12.8": ["cruisetours"], "5.7 7.9 12.4": ["cardiff"], "8.4 14.2 21.1": ["baltic"], "-6.0 8.3 0.6": ["diaconal"], "6.9 13.4 1.7": ["synchronizers"], "3.2 15.5 15.4": ["sarky"], "28.5 11.2 15.0": ["lassoes"], "10.9 6.9 11.1": ["thangkas"], "4.7 -2.9 17.5": ["jacksonville"], "4.3 3.3 12.7": ["zoot"], "21.1 -1.2 14.8": ["teakettles"], "3.8 -1.8 11.9": ["biss"], "3.3 22.0 9.5": ["tazered"], "2.5 16.4 9.7": ["laundresses"], "0.2 7.9 8.7": ["mazut"], "10.6 14.9 1.4": ["ensconsed"], "17.2 13.9 9.8": ["lockscreen"], "7.4 10.9 14.3": ["cremates"], "14.2 11.1 3.6": ["nebular"], "7.8 10.2 20.4": ["landraces"], "-3.3 -1.3 11.3": ["nonparents"], "11.4 6.1 20.5": ["yellower"], "12.9 0.9 -1.1": ["alrady"], "10.2 11.9 4.6": ["superhard"], "13.7 -1.8 17.8": ["vistor"], "8.4 9.9 29.7": ["caddisfly"], "-5.2 10.8 13.8": ["piecemealed"], "4.7 1.7 8.3": ["ratched"], "-3.2 2.5 7.1": ["resubdivision"], "14.5 6.3 23.3": ["reedbed"], "7.6 7.5 27.9": ["nightjars"], "4.8 5.5 12.4": ["chali", "leches"], "4.2 8.2 3.5": ["brattiness"], "7.2 7.4 5.0": ["prerevolutionary"], "9.7 12.8 13.7": ["moutain"], "17.7 3.0 24.1": ["cossie"], "0.4 0.9 11.0": ["sare"], "9.8 0.1 -2.1": ["presdient"], "6.1 13.3 8.1": ["guilting"], "18.8 14.3 14.4": ["lookie"], "-7.8 14.7 4.6": ["underdosing"], "6.8 25.6 10.1": ["assymetrical"], "8.8 18.8 20.3": ["microcracks"], "3.6 11.7 29.6": ["sauternes"], "-0.1 0.6 9.2": ["skinsman"], "-1.1 4.6 -1.2": ["decribes"], "-10.0 14.9 3.4": ["exegetes"], "9.4 1.3 -0.5": ["forhis"], "3.3 13.9 9.9": ["seria"], "1.1 -3.8 -4.2": ["spokersperson"], "5.6 10.9 37.3": ["warmwater"], "-8.9 9.8 11.0": ["optimality"], "-0.9 10.8 12.3": ["connie"], "-2.8 3.1 10.6": ["underbudgeted"], "-2.5 9.3 6.7": ["shakha"], "-7.6 9.2 6.8": ["upkeeping"], "9.1 12.9 20.8": ["polyphenolics"], "14.2 -2.5 4.4": ["superhigh"], "9.6 8.5 5.0": ["frenchman"], "5.0 8.8 11.9": ["kommer"], "12.6 22.0 9.0": ["sapient"], "0.9 0.6 -4.6": ["avariety"], "9.8 1.4 3.9": ["portacabins"], "5.2 4.3 13.4": ["hindlimb"], "0.5 12.5 9.2": ["nitty"], "-0.3 19.2 7.7": ["afriad"], "6.1 19.3 3.3": ["outbraking"], "-1.7 22.8 7.3": ["unhesitant"], "0.6 4.4 2.4": ["optmistic"], "-1.0 29.4 2.1": ["deployables"], "0.5 27.3 8.1": ["zapatista"], "1.8 22.8 1.5": ["impenitent"], "9.3 7.9 28.7": ["dragonfruit"], "13.6 7.9 4.0": ["shagger"], "12.6 4.5 12.4": ["crunked"], "3.8 15.9 12.6": ["fastbreaking"], "4.1 -0.7 6.1": ["multicharacter"], "19.4 -6.9 5.5": ["ukbetting"], "10.1 14.8 33.1": ["trematodes"], "3.5 1.4 3.6": ["behaviorial"], "-3.6 -4.4 1.7": ["crline"], "12.2 12.5 5.1": ["alarge"], "23.3 3.8 19.1": ["bikkies"], "12.6 24.2 15.9": ["meany"], "8.7 -7.3 23.1": ["hollowware"], "13.6 17.6 21.0": ["stingily"], "15.3 15.7 17.3": ["foetid"], "5.0 30.2 0.3": ["sieged"], "-0.4 9.5 9.2": ["rashi"], "-10.1 -3.0 2.0": ["selction"], "8.9 7.3 5.3": ["troublefree"], "5.9 5.3 14.4": ["tehbazari"], "4.0 14.1 37.7": ["gamebird"], "10.1 2.0 17.4": ["trackpants"], "2.3 17.5 18.8": ["livlihood"], "12.2 3.7 10.1": ["microprinting"], "-1.3 6.1 11.0": ["orissa"], "16.4 12.9 13.2": ["bourn"], "-2.7 -1.1 9.8": ["dzongda"], "-11.4 -1.3 -3.7": ["instatement"], "-1.4 -2.7 4.3": ["rish"], "-0.1 -6.2 5.4": ["webstreaming"], "-0.5 9.1 5.2": ["kano"], "15.7 -0.8 10.6": ["santo"], "10.5 -1.2 21.7": ["mui"], "5.6 -0.4 0.8": ["wouldnot"], "1.6 3.6 11.3": ["unconstructed"], "15.1 12.6 24.8": ["casuarinas"], "16.8 15.6 22.4": ["dipsy"], "3.1 8.1 7.2": ["thepotential"], "13.1 6.0 34.6": ["dimsum"], "-2.3 -0.0 6.8": ["concertizing"], "0.1 0.9 2.9": ["arised"], "8.3 7.6 29.3": ["savoriness"], "9.2 5.8 4.2": ["fractionate"], "19.8 5.1 0.0": ["emblazons"], "9.1 10.6 20.7": ["seaboards"], "15.2 7.1 14.2": ["blazered"], "-2.3 8.6 12.6": ["huwa"], "-3.0 3.7 10.1": ["hsuan"], "11.2 10.2 15.8": ["noblesse"], "-5.5 9.4 -4.7": ["eration"], "8.9 4.0 7.3": ["succcessful"], "17.5 23.3 8.4": ["grubbiest"], "10.5 15.2 14.4": ["wisenheimer"], "-3.0 8.5 10.9": ["endodontists"], "26.9 -2.6 3.5": ["megabrand"], "3.6 23.0 8.3": ["chatr"], "9.5 4.1 6.9": ["fille"], "-7.1 6.6 8.8": ["pumpage"], "18.0 4.3 31.5": ["yakiniku"], "-1.1 2.8 -0.5": ["officia"], "5.4 19.3 8.7": ["phsyical"], "16.4 11.8 5.0": ["unprecedent"], "18.8 12.7 6.6": ["onshoring"], "5.0 11.8 13.6": ["detoxifier"], "-0.5 2.4 6.8": ["retabulation"], "4.7 32.0 12.7": ["temporize"], "-1.9 10.7 7.7": ["cholecystitis"], "9.5 13.0 40.7": ["blacktips"], "5.1 1.0 0.6": ["ocal"], "8.9 -0.4 10.2": ["condotels"], "-1.2 10.3 8.6": ["subadvisors"], "7.9 -0.6 8.2": ["touchatag"], "-5.4 4.0 5.5": ["sahitya"], "25.7 -0.9 7.2": ["collapsable"], "8.0 6.2 15.4": ["sasha"], "5.5 10.4 27.0": ["tehina"], "-5.0 0.2 4.7": ["happythankyoumoreplease"], "-1.0 13.2 -1.9": ["ruhv"], "-3.3 10.1 9.5": ["dissipative"], "5.7 -7.2 3.5": ["perpetuals"], "-2.7 9.6 19.1": ["phylogenetically"], "-0.3 4.1 8.1": ["kilobases"], "2.6 12.0 22.5": ["stecklings"], "9.0 2.7 11.5": ["landbanking"], "2.0 5.8 2.4": ["analyzable"], "-0.3 8.4 3.4": ["abstractionists"], "9.7 19.3 5.5": ["subjectivities"], "11.0 13.9 8.4": ["htaccess"], "-1.8 9.5 22.9": ["whitewings"], "-3.0 2.4 3.7": ["apolipoproteins"], "12.2 17.1 11.1": ["recoupling"], "-1.0 -3.8 8.9": ["ures"], "7.8 6.3 25.2": ["qing"], "7.2 18.2 8.1": ["brusing"], "8.5 11.4 21.5": ["hairlessness"], "12.3 5.8 13.4": ["unreel"], "7.6 13.0 9.7": ["workprint"], "3.1 2.8 9.3": ["thur"], "5.7 12.0 2.6": ["sollen"], "8.7 11.4 8.5": ["dropsondes"], "4.0 17.6 6.3": ["getgo"], "-1.1 -10.0 -1.2": ["provisionary"], "-5.1 12.7 8.1": ["uz"], "15.9 2.2 18.2": ["benchpress"], "-1.9 3.4 8.7": ["hyperphosphataemia"], "4.6 5.5 16.5": ["admixed"], "16.3 9.0 5.9": ["scrollers"], "7.8 2.1 18.4": ["bart"], "5.6 6.2 17.9": ["whitney"], "-1.4 7.4 14.3": ["gthe"], "3.2 8.3 4.8": ["threerun"], "7.0 5.7 20.3": ["saudade"], "3.9 -2.0 -0.6": ["oney"], "17.3 7.2 12.9": ["pratfalling"], "19.2 27.5 11.6": ["necromancers"], "5.9 3.1 8.5": ["machinability"], "14.2 -1.0 19.2": ["flossy"], "4.2 -1.9 1.8": ["reshipped"], "7.4 10.1 4.8": ["conerns"], "3.1 4.1 2.0": ["interivew"], "-0.9 6.4 16.6": ["belltime"], "17.1 13.1 17.9": ["thirstily"], "2.5 4.2 9.0": ["unflooded"], "6.3 6.9 3.5": ["nonconvertible"], "-1.0 -1.8 0.1": ["colocating"], "8.6 3.4 -1.1": ["rthe"], "28.5 6.8 12.9": ["golfball"], "3.9 26.6 2.3": ["assimilative"], "-2.8 2.2 8.1": ["hypertonic"], "-6.8 7.8 0.7": ["inosine"], "7.3 22.1 13.1": ["trilemma"], "17.3 11.4 16.0": ["springboks"], "0.7 -8.6 13.6": ["kuen"], "3.4 18.9 38.2": ["gamebirds"], "0.4 9.2 15.0": ["liu"], "3.4 6.8 9.4": ["bezafibrate"], "7.6 22.6 11.1": ["karmas"], "-3.6 3.5 0.2": ["syndesmosis"], "19.8 10.5 4.4": ["fanzone"], "4.9 1.5 14.2": ["ropanis"], "4.7 -0.1 7.9": ["clazosentan"], "5.6 17.8 9.8": ["footedness"], "-2.6 13.6 1.3": ["campaining"], "9.5 3.7 17.9": ["medicinals"], "16.9 5.4 2.1": ["cladded"], "-5.0 18.8 1.0": ["injuires"], "12.7 9.9 9.7": ["ferromagnet"], "1.4 32.5 6.6": ["cunningness"], "9.8 23.8 3.6": ["thetans"], "3.6 9.9 5.9": ["pentavalent"], "1.6 8.7 2.2": ["contumacious"], "4.9 11.2 22.2": ["eutrophic"], "-3.3 0.4 7.5": ["hydrogeologists"], "14.9 10.3 5.8": ["centralizer"], "4.4 6.8 15.2": ["ergometers"], "8.1 9.4 -0.0": ["dilettantism"], "14.7 7.8 27.4": ["chaffinch"], "8.6 5.4 21.9": ["troweled"], "14.9 18.1 17.0": ["trembly"], "-4.0 17.6 11.4": ["defensing"], "-5.7 7.7 21.6": ["categoricals"], "3.2 -7.6 3.1": ["thd"], "-7.3 6.8 3.5": ["tractate"], "-3.3 7.1 7.4": ["pases"], "15.6 7.8 23.3": ["foodless"], "-12.3 -0.4 10.1": ["extractables"], "11.0 19.1 11.7": ["untransformed"], "-4.7 13.3 10.4": ["individualizes"], "3.9 18.6 6.5": ["demotivation"], "1.6 24.8 5.4": ["conciliating"], "6.0 5.8 17.6": ["damasks"], "2.8 12.8 1.9": ["bloviations"], "5.4 5.9 3.9": ["ecomii"], "3.4 14.0 19.8": ["taolu"], "-3.4 1.8 4.0": ["ouevre"], "3.5 11.0 13.1": ["bakra"], "4.7 9.7 19.1": ["hardstand"], "-1.8 8.5 1.1": ["oficer"], "5.0 4.2 5.1": ["ellos"], "-5.8 2.7 4.4": ["ascribable"], "-1.1 11.0 13.7": ["kayos"], "7.9 14.7 5.0": ["incomprehensive"], "0.2 10.8 3.2": ["gunshop"], "3.1 7.6 9.7": ["sophia"], "3.4 10.1 6.8": ["ush"], "-3.3 8.2 2.9": ["amifostine"], "5.6 13.3 -0.4": ["magnetostrictive"], "10.5 6.9 10.1": ["earpads"], "6.0 -5.0 2.9": ["witz"], "8.4 6.7 19.4": ["jeonse"], "0.4 13.0 16.0": ["acquifer"], "-0.3 5.0 13.2": ["haematopoietic"], "7.2 8.0 1.8": ["arbitraged"], "6.8 -3.0 10.3": ["dht"], "9.8 11.6 34.4": ["corkies"], "8.1 15.2 16.6": ["impassivity"], "4.8 7.1 19.5": ["armhole"], "22.1 9.2 11.9": ["popstrel"], "5.6 10.6 13.0": ["khiladi"], "5.6 25.8 6.1": ["oponents"], "-3.6 5.4 15.2": ["sakit"], "7.6 26.7 11.9": ["enfeebling"], "-10.6 4.1 9.2": ["sophmores"], "12.5 8.8 0.9": ["userfriendly"], "-4.8 12.8 9.0": ["regurgitations"], "7.4 15.4 5.7": ["penetratingly"], "-0.8 17.9 14.2": ["disquietude"], "27.9 2.7 0.5": ["protoype"], "12.0 6.4 19.8": ["bellydancer"], "-1.0 9.5 7.8": ["nonsecular"], "11.2 11.1 32.1": ["underparts"], "11.1 2.9 17.7": ["mog"], "24.6 16.8 27.0": ["mandrill"], "3.2 -3.2 2.7": ["vailable"], "22.0 11.7 19.4": ["cooldrink"], "12.0 19.4 22.3": ["fencerows"], "-6.0 1.4 5.4": ["ataxin"], "13.0 10.2 15.1": ["dipsomaniac"], "19.7 12.9 13.7": ["wimper"], "-3.2 15.1 11.2": ["roza"], "-0.1 1.9 15.8": ["buong"], "-6.9 7.1 8.4": ["skewness"], "12.6 5.6 23.7": ["strokers"], "3.7 1.5 2.6": ["degreee"], "12.6 23.5 15.3": ["overbalance"], "1.6 17.4 16.3": ["grandparenthood"], "7.3 11.7 4.5": ["innervate"], "-2.6 0.0 19.5": ["atong"], "9.0 12.5 13.0": ["riffy"], "4.3 -1.3 -2.8": ["stagiaire"], "6.1 9.1 18.1": ["siderite"], "1.3 13.1 8.4": ["demeanours"], "4.9 2.5 14.1": ["colza"], "14.4 9.2 38.3": ["piccalilli"], "-4.0 12.8 6.9": ["soceity"], "-8.9 4.1 8.2": ["kashrus"], "7.3 19.6 7.4": ["ungrudgingly"], "9.0 4.5 9.8": ["hospitalising"], "11.8 2.2 10.3": ["sweetners"], "17.1 7.5 17.9": ["acanthus"], "4.5 18.0 11.7": ["tikkun"], "0.5 6.5 2.4": ["kabbala"], "-0.2 12.4 5.5": ["abridgements"], "8.7 -1.0 8.9": ["vajazzling"], "16.3 0.9 8.3": ["roundoff"], "2.6 12.2 4.3": ["beasted"], "-4.5 10.9 0.3": ["subtopic"], "20.2 24.2 16.3": ["cloddish"], "1.3 -2.0 12.5": ["viss"], "4.0 -1.9 7.3": ["newyork"], "-2.2 7.6 9.6": ["devocalization"], "17.0 -0.9 6.6": ["reaccelerated"], "8.5 5.6 12.1": ["dylan"], "4.5 8.7 10.7": ["bloggin"], "14.1 15.0 22.8": ["chowhounds"], "19.5 6.1 18.1": ["breadmakers"], "8.2 7.6 5.9": ["cedent"], "9.6 7.4 4.9": ["midengine"], "11.4 14.4 17.1": ["spandrel"], "1.6 4.1 22.6": ["icewines"], "6.7 13.3 3.1": ["eventuating"], "13.1 10.4 33.6": ["cheesebait"], "7.3 20.0 19.6": ["hypermasculine"], "6.3 4.4 5.9": ["includin"], "2.0 11.3 32.0": ["blackcaps"], "4.0 2.0 5.1": ["matriculas"], "5.8 2.3 8.5": ["onyear"], "-8.9 13.8 6.6": ["aziz"], "21.9 10.5 18.9": ["dangler"], "1.5 7.0 8.2": ["piquantly"], "19.3 25.5 17.4": ["unnameable"], "2.1 3.0 3.2": ["stepout"], "5.5 12.5 11.1": ["vomitted"], "5.9 -1.5 1.2": ["druing"], "3.3 11.4 -0.3": ["ofall"], "8.1 4.1 -5.7": ["afternnon"], "19.2 8.2 19.4": ["acquatic"], "-10.6 11.4 5.0": ["commments"], "4.8 8.7 17.8": ["avifauna"], "2.9 41.4 2.6": ["aggressing"], "-9.0 6.0 -3.6": ["mifamurtide"], "3.3 22.4 5.8": ["oppenent"], "-0.1 2.4 4.1": ["sinologist"], "7.2 11.5 6.9": ["manganism"], "8.2 5.7 9.5": ["peseta"], "-1.9 18.0 16.0": ["guna"], "15.3 19.5 9.2": ["blackly"], "-0.2 3.2 11.6": ["mance"], "8.6 7.0 23.3": ["surreys"], "7.3 16.5 8.4": ["onball"], "1.8 -0.9 2.8": ["scho"], "7.1 7.1 9.7": ["pleasent"], "4.6 5.5 12.6": ["sportcoats"], "7.2 8.2 21.2": ["genetical"], "-7.6 9.9 2.6": ["qada"], "7.0 3.1 22.2": ["beefalo"], "13.3 13.0 25.2": ["guanacos"], "-0.4 19.7 6.9": ["glideslope"], "3.4 12.3 14.2": ["kapha"], "2.6 -8.3 5.7": ["todayat"], "2.5 8.2 17.7": ["gilbert"], "5.0 19.7 11.8": ["deterministically"], "8.6 1.4 3.5": ["athome"], "14.0 12.1 12.2": ["krazy"], "9.6 22.1 18.0": ["skys"], "4.6 16.1 -0.5": ["codings"], "12.6 10.6 18.0": ["crankin"], "4.0 6.8 3.0": ["mvision"], "11.4 12.4 24.6": ["cooch"], "-1.7 -1.8 7.0": ["reverification"], "8.2 12.9 14.2": ["cydia"], "-5.4 11.8 12.9": ["thymocytes"], "5.8 13.3 12.9": ["clannishness"], "-0.9 12.6 13.7": ["flavivirus"], "2.1 10.6 17.1": ["uss"], "15.6 11.0 11.4": ["aeries"], "-2.8 23.7 -2.8": ["abjures"], "22.9 16.5 20.6": ["floorless"], "13.3 3.6 18.0": ["jf"], "11.9 10.0 12.3": ["scarved"], "8.7 6.0 6.4": ["dtac"], "2.9 4.6 11.6": ["guitarwork"], "0.1 7.9 -4.4": ["appauled"], "22.8 9.9 7.9": ["oogle"], "9.4 3.1 3.3": ["issu"], "12.7 20.5 29.6": ["mizzen"], "12.2 11.2 12.9": ["hotfooting"], "19.3 12.2 16.9": ["gavotte"], "6.3 10.7 19.6": ["tzu"], "1.2 9.5 2.4": ["generativity"], "14.8 17.8 4.9": ["misalign"], "3.5 -1.9 6.9": ["edeus"], "4.4 13.5 13.0": ["neuroglobin"], "14.3 13.4 31.5": ["mealies"], "21.7 3.7 20.2": ["mooed"], "8.6 19.5 19.0": ["desertified"], "18.1 3.7 20.8": ["coopering"], "-1.5 11.3 9.8": ["felicities"], "10.7 10.5 14.6": ["inducingly"], "5.4 20.0 10.5": ["narcotized"], "-0.1 11.5 11.6": ["nonurban"], "7.2 0.3 5.4": ["angelo"], "3.1 18.2 5.9": ["mediaman"], "2.6 0.6 12.4": ["aquathlon"], "4.0 2.1 15.9": ["gigalitre"], "2.8 8.4 22.5": ["matzot"], "3.4 5.9 13.5": ["vpn"], "-0.1 16.3 6.5": ["disrepectful"], "5.8 -2.7 -3.5": ["marzo"], "17.9 8.4 10.2": ["endzones"], "4.0 9.4 15.2": ["ingrowth"], "13.9 10.5 28.0": ["ferruginous"], "3.8 9.1 10.0": ["dandyism"], "2.2 12.3 7.2": ["downconverter"], "10.5 2.7 18.4": ["pastilles"], "3.6 5.4 9.1": ["wekend"], "2.0 6.8 -1.4": ["directer"], "8.1 11.6 22.5": ["egger"], "5.2 3.7 -0.2": ["batteryless"], "4.2 13.2 6.4": ["sectorals"], "5.4 10.0 13.2": ["rainbands"], "-4.0 2.9 6.7": ["carroll"], "2.7 7.1 1.0": ["kommen"], "3.4 10.0 0.3": ["antiarrhythmic"], "0.2 8.7 10.3": ["confict"], "-4.2 7.9 7.4": ["bromocriptine"], "16.7 18.3 14.4": ["gouger"], "11.5 18.3 9.2": ["histrionically"], "17.0 10.9 19.1": ["richie"], "-3.2 21.5 3.5": ["ayat"], "9.8 12.2 8.4": ["caravaning"], "15.3 11.5 27.6": ["greeny"], "20.2 10.7 30.1": ["wursts"], "11.7 15.6 17.5": ["boozes"], "4.1 16.7 -1.5": ["redefinitions"], "5.7 -5.0 -3.2": ["ims"], "7.9 7.6 7.9": ["nucleobases"], "-6.6 1.3 4.2": ["sdb"], "-7.1 11.5 18.5": ["chet"], "15.6 6.2 16.7": ["trancey"], "8.7 9.4 14.3": ["blokeish"], "15.7 9.8 15.8": ["caballero"], "6.3 12.6 17.3": ["juicily"], "11.7 12.7 5.5": ["potentional"], "17.4 2.5 44.2": ["muktuk"], "-0.3 4.5 6.8": ["sory"], "11.6 17.2 1.5": ["resiliance"], "20.6 22.7 22.0": ["swashbuckle"], "-0.9 2.5 21.9": ["malbecs"], "6.5 14.2 10.5": ["hypertechnical"], "-2.8 -0.7 0.9": ["musicalization"], "9.2 13.2 6.2": ["overweighed"], "5.3 1.9 28.8": ["deglazed"], "-1.9 19.0 8.6": ["anthracis"], "-2.7 12.0 9.2": ["adulteries"], "9.2 14.9 4.1": ["astrovan"], "0.8 5.4 14.2": ["canalphones"], "3.1 7.5 2.6": ["bijli"], "11.5 7.5 6.9": ["roadblocked"], "7.8 9.2 10.4": ["epicene"], "6.2 27.3 11.7": ["submunition"], "6.3 14.1 10.1": ["officialese"], "10.0 4.3 14.2": ["anway"], "8.3 0.7 26.6": ["dragonboat"], "9.9 3.4 7.1": ["lightrail"], "3.0 33.5 5.2": ["splittists"], "1.3 2.7 8.2": ["kibitzed"], "18.3 11.8 38.1": ["anhinga"], "2.5 2.6 17.4": ["stylers"], "16.3 -2.4 17.6": ["craftworks"], "9.6 3.5 -2.6": ["fiancial"], "0.4 12.6 6.0": ["goaless"], "15.5 18.5 18.3": ["dobermans"], "14.2 11.9 21.3": ["bunchy"], "15.7 14.5 3.2": ["inveigling"], "4.6 11.0 12.8": ["spikiness"], "2.3 20.5 9.9": ["bureaucratisation"], "-1.1 14.9 14.1": ["haphazardness"], "15.2 3.9 12.7": ["breasting"], "15.3 4.2 36.0": ["brochette"], "-6.3 3.9 8.3": ["pendimethalin"], "22.0 4.3 9.9": ["superband"], "19.7 -0.4 -6.5": ["baed"], "22.6 5.4 11.6": ["livedoor"], "11.9 15.7 0.6": ["dematerialize"], "11.0 2.3 7.3": ["unclogs"], "8.3 3.8 24.9": ["neotropical"], "8.2 14.8 17.1": ["superhorse"], "19.3 -1.3 16.8": ["guiro"], "3.1 14.5 10.1": ["surving"], "14.5 4.5 23.8": ["gorp"], "12.2 11.6 9.9": ["maximizers"], "0.9 5.8 12.8": ["liao"], "24.3 34.7 13.1": ["berserkers"], "20.7 10.1 35.2": ["profiterole"], "16.3 22.6 22.7": ["brainpan"], "2.9 5.4 5.2": ["minuts"], "-1.5 5.4 7.2": ["choreopoem"], "2.9 3.2 5.2": ["politiques"], "2.2 5.1 5.4": ["cpp"], "12.8 13.7 11.4": ["dripline"], "10.7 9.5 15.6": ["carrick"], "-9.3 8.6 8.6": ["penology"], "-12.5 -3.4 5.8": ["restudied"], "5.6 7.3 13.9": ["woodframe"], "-9.4 1.1 5.0": ["establised"], "2.0 11.3 13.9": ["gettng"], "2.7 6.7 10.3": ["cathodic"], "16.2 1.4 -0.3": ["ankling"], "5.2 5.7 15.9": ["paleoclimatic"], "5.1 12.9 13.7": ["splain"], "1.6 14.3 7.0": ["rallygoers"], "-3.6 -0.4 2.9": ["antedated"], "-3.9 2.4 15.0": ["cyberschools"], "3.8 8.7 15.8": ["hearting"], "10.4 26.5 1.0": ["barage"], "5.7 11.1 13.3": ["drywalled"], "8.8 1.5 40.4": ["blackfin"], "6.2 5.2 7.4": ["superlattices"], "5.6 16.9 7.0": ["instrumenting"], "8.1 3.0 15.8": ["toked"], "3.2 18.3 1.5": ["reconsolidated"], "0.1 -7.6 12.8": ["minigrants"], "6.1 7.6 3.9": ["clockless"], "8.1 13.3 16.1": ["nolan"], "10.5 10.3 11.8": ["superfeatherweight"], "12.7 13.5 10.2": ["hobbyhorses"], "1.7 -0.8 19.3": ["rehri"], "5.1 9.1 8.4": ["hydrogenase"], "8.8 6.0 -0.7": ["hasd"], "8.2 0.2 8.0": ["highschoolers"], "11.2 16.6 22.1": ["rills"], "19.7 12.3 28.5": ["kickboards"], "9.0 10.4 31.2": ["bhindi"], "11.6 6.4 13.2": ["cornrowed"], "17.2 13.3 11.9": ["knackering"], "18.3 30.4 12.0": ["terraform"], "9.9 7.3 15.7": ["shirtwaist"], "10.5 -0.7 5.7": ["callgirl"], "8.0 11.8 14.3": ["vorticity"], "8.2 21.0 11.9": ["pensiveness"], "12.8 17.3 8.5": ["flaneur"], "0.4 2.1 15.3": ["jaaye"], "-4.8 11.5 0.7": ["salvations"], "0.4 22.3 3.4": ["ideational"], "-0.7 4.7 5.4": ["permeabilities"], "-0.3 7.5 4.7": ["promulgations"], "9.3 13.1 15.5": ["fuego"], "9.1 6.3 1.3": ["prominance"], "3.1 15.4 11.1": ["charterhire"], "3.0 5.6 4.3": ["unawarded"], "8.7 8.9 10.7": ["trippier"], "9.7 7.3 5.6": ["ecotel"], "9.3 6.0 30.1": ["tartine"], "-3.7 0.7 7.4": ["anatase"], "11.8 6.6 2.6": ["runarounds"], "11.7 1.9 10.3": ["repoint"], "11.6 15.3 6.5": ["kaffiyehs"], "4.6 6.9 -1.0": ["newswomen"], "16.0 -1.3 2.8": ["dolars"], "1.2 11.9 11.1": ["overconsume"], "9.8 9.6 6.3": ["peptidoglycan"], "13.2 -1.3 12.2": ["heatable"], "-3.8 7.5 7.0": ["heirship"], "3.7 6.4 20.9": ["mezzotint"], "14.3 7.7 3.3": ["ressurect"], "6.3 14.2 29.9": ["intracoastal"], "5.9 5.1 5.4": ["briberies"], "5.9 13.5 6.7": ["sensical"], "4.1 6.5 14.0": ["balletomanes"], "3.3 15.0 18.1": ["eudialyte"], "12.2 6.7 31.2": ["nonpareils"], "10.9 10.3 38.8": ["romesco"], "8.9 16.1 13.6": ["blockaders"], "4.9 1.8 12.5": ["wahr"], "12.9 39.5 12.8": ["starfighter"], "-0.2 -4.0 9.7": ["environnement"], "11.8 10.0 8.3": ["cocksucking"], "10.6 12.1 18.2": ["clearfelling"], "6.3 20.1 -1.8": ["motional"], "15.1 15.7 14.4": ["wasteground"], "12.4 -1.0 11.6": ["pasa"], "-2.7 5.2 8.4": ["tracheotomies"], "7.4 4.8 7.8": ["tolevamer"], "10.6 40.1 21.3": ["grenadiers"], "16.1 3.6 7.9": ["mishitting"], "19.2 4.2 29.3": ["stuffies"], "11.7 13.6 14.7": ["gibber"], "14.0 -3.4 9.4": ["fullservice"], "7.6 0.9 6.8": ["xhtml"], "12.9 5.3 2.1": ["kafuffle"], "4.2 6.8 1.0": ["helath"], "9.6 -0.5 6.6": ["flix"], "-1.6 1.8 8.1": ["signoffs"], "12.1 10.1 18.2": ["joshua"], "-9.8 19.0 2.9": ["occurrance"], "9.2 13.9 8.3": ["massy"], "3.4 12.5 6.3": ["enmass"], "-4.6 -1.2 16.4": ["kadi"], "3.6 10.1 8.1": ["betweeners"], "9.3 21.2 6.4": ["seeth", "civvy"], "-16.8 5.5 5.1": ["preservice"], "18.0 -0.2 7.2": ["extravanganza"], "13.3 21.2 9.2": ["immovably"], "7.8 4.0 6.9": ["drlg"], "15.6 6.9 22.9": ["kips"], "23.3 16.1 29.1": ["tailfeathers"], "-1.9 15.7 5.9": ["ostium"], "5.0 2.7 19.1": ["chapeaux"], "2.7 16.6 8.0": ["perorations"], "-1.0 2.3 6.5": ["osteogenic"], "2.2 18.7 16.6": ["mistimes"], "11.3 -1.7 1.6": ["missold"], "3.3 9.0 11.2": ["tibula"], "18.4 7.3 5.0": ["subediting"], "4.1 2.0 7.3": ["praseodymium"], "10.0 10.8 19.9": ["begger"], "4.9 3.7 17.5": ["chipless"], "9.6 22.8 21.3": ["mildews"], "-3.6 5.8 4.5": ["sensitizer"], "3.8 16.6 14.9": ["legi"], "-7.2 1.8 -7.1": ["exerpts"], "-3.6 12.8 10.2": ["predecease"], "12.8 10.8 17.0": ["deva"], "19.5 5.3 9.4": ["murderesses"], "2.4 3.4 9.2": ["quar"], "-7.7 6.0 3.8": ["pyrazinamide"], "3.2 -4.0 -1.0": ["theopportunity"], "9.1 12.9 19.0": ["denned"], "13.4 0.5 29.0": ["shantung"], "1.9 2.7 8.4": ["sextets"], "2.2 5.1 8.2": ["mariage"], "10.3 4.5 8.0": ["bdsm"], "13.7 13.7 3.0": ["airbrake"], "14.3 1.5 23.0": ["microbrewer"], "5.4 0.5 4.5": ["peuvent"], "5.6 10.3 8.5": ["crise"], "4.6 4.1 7.3": ["bangkok"], "8.6 6.2 0.3": ["recognizeable"], "0.4 10.6 3.6": ["detenu"], "13.5 11.5 22.6": ["tardigrades"], "-0.5 9.0 7.3": ["settlors"], "-1.1 9.0 6.4": ["punya"], "5.7 12.6 12.9": ["punster"], "3.5 18.5 9.3": ["trifurcated"], "8.6 16.2 8.7": ["forwad"], "12.3 15.4 11.4": ["frazzling"], "-3.8 18.7 5.3": ["cathartically"], "17.1 7.0 5.1": ["eers"], "3.9 2.8 4.6": ["livestats"], "4.3 26.0 -1.8": ["bogusly"], "9.0 10.5 2.9": ["rockist"], "14.1 6.6 13.7": ["abaft"], "-3.4 2.8 11.2": ["ously"], "0.9 8.4 14.5": ["threeball"], "4.3 15.1 14.5": ["negros"], "17.8 11.2 5.9": ["cyclinders"], "14.0 14.3 9.2": ["outleaping"], "8.4 12.0 -9.8": ["indpendent"], "-0.7 10.9 9.0": ["segements"], "6.7 2.1 10.5": ["mips"], "5.8 4.5 4.0": ["dropdowns"], "15.3 7.0 30.9": ["strombolis"], "2.7 15.1 5.2": ["anticlerical"], "4.8 10.2 15.9": ["hematitic"], "12.3 10.2 -2.3": ["mischaracterised"], "-0.5 3.6 2.7": ["echogenicity"], "6.3 6.0 1.9": ["stongly"], "-2.9 1.3 3.9": ["suspened"], "11.4 10.4 28.7": ["redstarts"], "-0.4 21.9 5.8": ["inteligent"], "6.8 17.4 8.8": ["vexingly"], "2.5 1.1 -2.4": ["appel"], "6.4 6.9 7.2": ["mmbo"], "11.5 13.8 15.9": ["offbreak"], "4.4 9.7 2.3": ["autobio"], "7.8 15.1 19.6": ["fumarole"], "20.7 13.2 4.7": ["seens"], "-1.0 6.2 6.0": ["haan"], "0.3 2.7 12.6": ["polychlorinated"], "6.3 14.5 17.8": ["airboaters"], "14.4 20.5 20.2": ["silverbacks"], "6.6 21.9 6.1": ["gruntled"], "2.7 20.3 7.5": ["painfull"], "10.3 6.8 16.4": ["immunoprecipitation"], "8.7 12.0 15.1": ["sht"], "31.2 4.6 26.1": ["apatosaurus"], "15.0 14.0 9.0": ["drabbest"], "18.4 3.3 31.8": ["icehouses"], "1.1 15.5 11.1": ["vitilligo"], "-4.7 8.3 -4.1": ["suberb"], "-2.8 13.2 6.4": ["presidentiable"], "3.5 14.0 10.5": ["perserve"], "11.4 1.4 10.4": ["sueded"], "-3.0 16.6 4.3": ["worng"], "3.5 13.3 10.0": ["vaccinator"], "7.0 11.3 8.2": ["girlfiend"], "20.2 8.1 7.9": ["poncing"], "-1.0 10.1 1.9": ["conductress"], "7.3 6.3 13.1": ["leverageable"], "4.3 18.2 2.9": ["liberalist"], "9.3 2.4 3.5": ["subcomittee"], "5.2 6.4 5.8": ["xrays"], "11.3 8.0 7.4": ["darkwave"], "6.9 4.1 6.0": ["donts"], "10.5 0.6 -3.8": ["financialservices"], "-8.5 6.7 6.1": ["pyrimethamine"], "7.3 1.8 -5.4": ["andfinancial"], "7.5 13.4 8.2": ["chupah"], "1.0 27.1 10.2": ["embitters"], "-0.9 -3.8 -3.8": ["areavailable"], "18.5 16.2 9.1": ["aircaft"], "12.7 23.0 1.8": ["airbourne"], "14.1 1.2 1.1": ["nondelivery"], "1.3 6.1 -1.1": ["selon"], "9.5 10.6 16.5": ["daddys"], "26.6 8.3 22.1": ["weblike"], "10.7 2.5 7.5": ["nord"], "11.2 -2.7 12.2": ["cittern"], "-0.9 4.4 8.9": ["makereadies"], "13.8 7.6 9.2": ["centrefolds", "billie"], "7.3 10.7 10.8": ["engineman"], "-5.1 4.9 14.4": ["gallonage"], "23.5 2.2 7.4": ["themepark"], "6.6 7.4 8.6": ["gentlewomen"], "-5.8 5.8 2.7": ["cyclohexanone"], "-3.2 2.7 6.0": ["hypopharynx"], "-8.2 5.0 8.9": ["acetochlor"], "-7.7 -4.3 7.1": ["reunifications"], "7.4 6.4 16.6": ["teo"], "-0.5 13.3 11.2": ["miniaturists"], "18.6 18.8 27.2": ["foremast"], "2.7 8.6 6.0": ["defragments"], "4.1 12.9 15.1": ["outride"], "11.7 8.9 26.0": ["biomasses"], "11.0 8.1 35.3": ["cardoons"], "10.4 7.4 7.0": ["miff"], "1.7 9.7 6.9": ["iff"], "5.9 -7.4 1.5": ["inclue"], "3.8 2.1 5.7": ["substancial"], "7.8 13.5 -0.6": ["derangements"], "4.4 9.6 13.8": ["parotid"], "21.2 14.0 8.2": ["counterbidder"], "2.6 20.2 10.6": ["uncurious"], "-1.6 -0.9 7.2": ["daughterboard"], "5.7 0.9 5.4": ["overcollected"], "7.2 14.4 24.0": ["ducker"], "1.3 12.2 10.4": ["chromaticity"], "11.8 12.5 3.8": ["microbattery"], "14.4 1.4 12.7": ["commingles"], "-2.5 10.7 14.3": ["repealer"], "-0.9 6.7 4.8": ["isssues"], "12.7 2.6 15.0": ["benchtops"], "13.3 16.8 12.9": ["ishness"], "8.8 5.7 12.8": ["vibro"], "5.3 -6.1 -2.2": ["offeres"], "9.7 8.9 6.9": ["cableless"], "9.8 17.7 3.3": ["stereoscopy"], "-3.3 15.2 7.3": ["midcourters"], "13.7 2.9 6.9": ["erst"], "-6.3 18.9 2.8": ["exilic"], "16.6 7.3 14.2": ["tricot"], "1.0 -6.6 7.7": ["lifed"], "8.7 20.5 12.2": ["puissant"], "4.1 20.6 6.9": ["unspiritual"], "0.1 9.9 6.4": ["microhydro"], "17.7 16.3 13.3": ["topes"], "-1.1 4.0 17.6": ["oen"], "-3.4 33.4 5.5": ["assasinations"], "4.2 11.8 14.7": ["gonzalez"], "-6.4 4.5 -0.2": ["expatiated"], "10.9 7.5 25.8": ["waterskiers"], "1.0 -3.7 6.3": ["mastertones"], "18.7 19.3 18.5": ["parachuter"], "27.1 5.4 8.1": ["advertsing"], "1.1 8.2 13.1": ["brgy"], "-3.4 19.8 9.7": ["kalaban"], "3.0 6.9 8.9": ["berbatov"], "19.3 3.8 5.1": ["airbeds"], "14.7 13.4 22.3": ["xeno"], "22.0 6.2 23.0": ["whiffleball"], "12.4 16.0 23.8": ["desalinator"], "17.8 18.5 16.6": ["bushrangers"], "13.6 11.4 14.6": ["lucent"], "8.1 13.8 6.3": ["afterimage"], "1.9 20.7 -1.4": ["swingby"], "8.0 20.0 16.2": ["tachiai"], "8.7 16.6 11.6": ["juggalos"], "13.7 16.5 10.7": ["humm"], "10.2 6.2 21.7": ["coppiced"], "6.2 16.4 3.1": ["counterblast"], "3.9 6.7 29.1": ["ula"], "14.2 18.2 9.0": ["cracy"], "5.9 8.3 10.3": ["herion"], "2.9 8.6 3.7": ["taribavirin"], "7.0 1.9 5.4": ["nuevas"], "-1.9 11.5 9.7": ["perivascular"], "2.4 3.4 22.3": ["farrowings"], "-4.2 7.0 7.7": ["escrowing"], "14.5 13.5 11.1": ["habbit"], "11.6 12.2 22.3": ["overeater"], "5.4 5.5 15.4": ["xenoliths"], "0.9 11.5 11.7": ["showhorse"], "-1.3 -8.1 0.7": ["customerservice"], "10.3 11.5 24.7": ["subducting"], "15.4 20.4 16.4": ["excrescence"], "7.5 14.3 0.2": ["ostracisation"], "10.7 12.1 32.5": ["perilla"], "3.8 18.2 9.3": ["ethnos"], "11.1 11.9 10.4": ["unrecognisably"], "3.0 10.7 3.1": ["whre"], "4.8 11.0 11.2": ["ditchwater"], "11.6 22.7 37.7": ["yellowjacket"], "9.5 15.1 6.1": ["surefootedness"], "12.7 6.8 11.9": ["ugar"], "11.9 2.2 -1.4": ["electronical"], "-0.5 13.8 19.7": ["butches"], "9.6 10.1 25.3": ["rubra"], "1.8 9.4 11.2": ["humectants"], "7.3 9.6 -0.2": ["contolled"], "-0.7 11.1 14.0": ["sifu"], "6.4 11.9 14.0": ["initiatory"], "-1.1 16.3 15.1": ["clubroot"], "-0.3 14.9 -2.3": ["inadvisability"], "13.0 2.1 11.8": ["streetdance"], "10.8 13.4 20.1": ["watermaker"], "12.6 9.2 20.6": ["carousal"], "10.9 17.7 10.0": ["furtiveness"], "3.7 7.7 13.2": ["augmentin"], "-1.4 15.1 5.1": ["dhcp"], "7.7 6.6 20.9": ["atlatls"], "7.7 21.3 7.4": ["bluenoses"], "-0.0 18.1 10.1": ["probie"], "16.3 -5.3 5.8": ["treet"], "-3.1 16.2 10.1": ["colorism"], "7.4 9.2 8.7": ["blackmarketing"], "6.5 17.7 15.0": ["atl"], "18.4 6.7 31.6": ["sammies"], "21.1 15.2 24.9": ["whelps"], "11.1 4.0 51.7": ["saithe"], "0.0 -7.1 5.2": ["receieve"], "3.2 19.9 24.4": ["northwesterlies"], "9.2 -0.0 13.8": ["botanicas"], "4.9 8.0 16.4": ["kelvins"], "9.6 7.6 38.1": ["gougeres"], "10.3 9.1 24.8": ["kopitiam"], "4.4 14.3 0.1": ["organizaton"], "1.9 -2.7 4.6": ["entinostat"], "-3.1 11.2 12.9": ["hydrocele"], "6.9 1.8 20.7": ["papel"], "14.4 -1.3 10.1": ["superschool"], "8.8 -3.6 0.1": ["previosuly"], "3.5 10.2 7.9": ["glycyrrhizin"], "2.5 18.1 -1.6": ["drumbeating"], "4.9 11.1 12.3": ["egde"], "-0.0 8.2 8.5": ["incorrigibility"], "-5.5 1.6 1.7": ["sabhadhipati"], "8.2 -0.8 15.2": ["pudgier"], "25.2 16.1 15.5": ["tardis"], "11.6 21.4 28.5": ["outswim"], "2.3 19.0 9.6": ["nonplayoff"], "5.6 9.5 15.1": ["uncropped"], "-1.6 22.4 14.2": ["gunowners"], "5.8 25.2 16.1": ["rudos"], "12.5 16.5 16.8": ["blondness"], "0.3 8.9 -0.8": ["machen"], "2.8 7.7 -3.6": ["veteren"], "8.6 1.2 9.5": ["corey"], "19.2 16.2 7.9": ["imagineers"], "-0.7 9.5 5.5": ["praveen", "prabhari"], "-8.5 1.3 3.9": ["ences"], "10.6 4.0 20.3": ["premeasured"], "-2.2 10.6 6.7": ["moulage"], "11.8 3.4 25.8": ["crucifer"], "2.9 12.7 -4.4": ["forgeting"], "11.8 10.0 20.8": ["rootlets"], "14.1 12.4 43.9": ["shucker"], "9.2 8.9 10.4": ["potless"], "5.0 15.1 10.3": ["postfeminist"], "-0.3 12.6 8.9": ["reversers"], "14.1 2.7 28.3": ["sourwood"], "2.5 4.6 13.7": ["unoxidized"], "1.8 1.8 7.9": ["scooterette"], "-2.1 10.1 7.0": ["zakah"], "-2.2 4.9 13.0": ["cefuroxime"], "14.5 7.6 20.4": ["cubers"], "12.4 0.3 9.7": ["vibram"], "10.1 5.3 24.2": ["briquets"], "10.0 2.7 -4.3": ["signifcantly"], "-1.8 0.8 0.4": ["dence"], "-2.7 12.2 11.3": ["qawalli"], "-1.2 12.4 10.0": ["flexors"], "-3.5 6.2 -1.8": ["possitive"], "9.1 13.6 8.3": ["videshi"], "-8.6 27.0 13.9": ["augmentees"], "-1.6 -6.7 4.6": ["resultof"], "14.8 5.8 20.0": ["flatcars"], "14.6 11.2 14.0": ["rop"], "6.5 0.6 13.6": ["kuang"], "-6.1 5.2 -0.0": ["subtest"], "2.9 -2.0 8.6": ["stakeswinners"], "16.1 9.9 13.1": ["pinking"], "1.5 9.5 3.3": ["thers"], "3.9 7.6 5.4": ["upcoding"], "-4.6 21.4 2.1": ["scenerios"], "8.9 1.2 3.2": ["operat"], "0.5 0.9 10.9": ["ination"], "17.0 11.3 14.3": ["instos"], "6.4 4.2 5.0": ["axings"], "5.8 17.5 12.5": ["metaphysic"], "-4.2 -4.1 10.9": ["postjudgment"], "-6.3 21.6 8.9": ["biotype"], "10.6 -1.2 15.9": ["tudor"], "6.7 6.4 7.4": ["ngos"], "-0.1 13.6 7.6": ["perpective"], "16.9 -0.9 6.4": ["nelle"], "-4.6 8.2 -3.3": ["investgation"], "4.1 23.4 14.4": ["hardheadedness"], "16.6 15.4 15.9": ["diningroom"], "-1.2 1.9 15.3": ["genebanks"], "3.0 9.4 8.8": ["connectionless"], "5.9 12.6 9.4": ["waymarked"], "10.5 15.7 17.9": ["canis"], "1.0 0.9 4.7": ["dermatopathology"], "4.8 5.5 12.0": ["regreening"], "15.5 4.9 22.2": ["biosecure"], "7.4 17.8 8.3": ["incredulousness"], "6.8 19.5 5.1": ["ethnocide"], "11.3 7.2 26.5": ["chinkaras"], "18.6 8.3 24.9": ["hornpipes"], "7.4 -4.6 25.6": ["rawhides"], "8.0 4.7 13.1": ["folkdance"], "9.7 7.8 8.7": ["aerobars"], "12.3 2.6 28.2": ["pimenton"], "16.9 11.2 25.8": ["chaffinches"], "13.9 9.8 5.8": ["anechoic"], "15.1 7.5 14.7": ["drivethrough"], "-4.1 2.9 12.7": ["direk"], "1.6 6.2 10.3": ["blook"], "2.3 10.3 0.9": ["euromicron"], "-4.6 8.7 1.4": ["granthi"], "-0.9 22.7 2.2": ["inoperability"], "10.2 3.8 21.5": ["stephanotis"], "8.3 13.7 3.5": ["philo"], "9.5 6.6 3.4": ["avataar"], "17.6 28.5 29.2": ["hornworms"], "2.1 3.1 8.9": ["rebookings"], "10.2 11.6 20.2": ["unbend"], "10.2 2.7 29.6": ["gingersnap"], "10.9 5.7 -0.9": ["yesterda"], "-2.8 10.7 3.6": ["necessitous"], "8.0 3.5 33.1": ["hypertufa"], "2.2 -1.9 3.9": ["whick"], "2.9 6.0 3.9": ["undepreciated"], "11.4 5.0 12.1": ["yearago"], "-0.3 5.5 19.8": ["feedgrain"], "9.2 9.7 48.6": ["longfin"], "1.7 -0.1 12.1": ["sauf"], "7.0 12.0 10.7": ["overdraws"], "-3.3 9.3 3.1": ["prearrangement"], "12.0 12.2 32.2": ["morays"], "0.0 7.5 16.4": ["pyrimidine"], "-4.6 -4.3 -0.4": ["preapplication"], "-4.1 9.5 -0.3": ["profil"], "14.9 7.9 5.9": ["indonesian"], "18.2 10.1 16.6": ["quaintest"], "25.2 27.3 14.7": ["planetwide"], "-3.2 3.4 2.8": ["incyclinide"], "-6.0 1.7 6.2": ["breathiness"], "16.0 7.3 17.8": ["magicked"], "7.5 13.3 6.0": ["giallorossi"], "3.3 9.5 30.5": ["basils"], "4.6 9.9 11.5": ["hipsterism"], "16.8 5.3 4.1": ["nanofibre"], "13.5 3.9 13.4": ["architraves"], "13.2 25.9 7.4": ["buddie"], "-3.1 12.6 6.3": ["cromolyn"], "6.5 9.0 23.7": ["instar"], "19.3 12.7 33.3": ["pukeko"], "-0.2 -0.5 -1.2": ["micturition"], "-2.3 7.5 1.6": ["intermodulation"], "42.1 17.1 10.3": ["megacorporation"], "2.8 4.8 -3.0": ["dazu"], "10.4 -0.3 14.6": ["photogravure"], "14.8 8.9 8.9": ["shrilled"], "18.0 2.0 14.8": ["jittered"], "-12.0 3.0 4.8": ["probational"], "15.1 20.4 9.9": ["catchfence"], "12.4 12.2 16.2": ["mildewy"], "7.7 13.9 11.7": ["raha"], "9.9 15.8 19.1": ["taciturnity"], "23.4 17.4 17.0": ["ilomilo"], "-1.5 7.9 13.9": ["metallurgically"], "13.0 17.0 16.9": ["elbowdrop"], "6.0 1.6 -0.8": ["gaoled"], "6.6 14.5 5.1": ["erythroid"], "1.5 12.8 9.5": ["ida"], "4.7 12.6 3.3": ["radiosity"], "-3.2 12.5 3.8": ["theteam"], "6.8 7.7 8.1": ["etwas"], "16.9 -1.4 -1.8": ["fmcg"], "1.3 15.1 10.9": ["elisions"], "2.4 19.7 17.9": ["semantical"], "9.0 30.7 9.2": ["backburns"], "14.4 11.5 17.8": ["kudus"], "5.6 1.0 0.3": ["comeptition"], "0.7 10.3 5.8": ["expierence"], "9.5 1.4 9.6": ["mathlete"], "8.2 12.4 5.8": ["shrinked"], "-9.4 1.5 3.3": ["timepoints"], "15.8 -7.2 -0.7": ["meldt"], "-0.4 8.0 8.2": ["pandu"], "-5.4 -5.4 -1.1": ["fered"], "1.4 10.8 9.4": ["dman"], "21.5 12.2 38.2": ["frankenfish"], "-5.4 16.4 17.3": ["vata"], "18.5 4.2 17.9": ["reeded"], "4.3 7.9 16.9": ["nalang"], "15.3 10.0 11.7": ["thermic"], "6.9 0.3 7.1": ["frontperson"], "-3.1 -2.5 16.3": ["pima"], "-2.2 0.6 12.4": ["expcted"], "16.3 17.9 11.2": ["thumpingly"], "8.9 9.9 14.3": ["boffing"], "1.6 11.9 10.6": ["transmen"], "-2.8 4.8 10.5": ["scorecast"], "9.4 10.4 2.6": ["inexhaustibly"], "2.1 11.7 3.9": ["airpacks"], "6.8 4.5 19.4": ["sunoil"], "10.3 -0.5 8.2": ["calcining"], "-2.0 4.7 7.2": ["excos"], "8.7 5.9 15.2": ["fructans"], "3.5 15.6 5.7": ["answerers"], "11.5 18.3 9.9": ["undeployed"], "18.1 8.8 22.0": ["dullish"], "9.6 1.6 1.9": ["pwr"], "15.7 6.0 -0.6": ["cloistering"], "6.9 2.8 18.9": ["remelting"], "13.9 10.5 7.9": ["starmaker"], "6.1 19.4 17.7": ["gnarlier"], "-4.6 1.5 0.3": ["perfusionists"], "5.0 10.7 12.0": ["asli"], "0.2 13.9 4.9": ["hearteningly"], "12.5 23.5 15.3": ["untrodden"], "6.3 16.9 12.7": ["hogtying"], "-0.8 10.5 4.3": ["papacies"], "2.0 12.9 12.7": ["climacteric"], "11.2 3.1 6.8": ["electrodynamic"], "10.7 2.7 0.9": ["dragstrips"], "9.0 5.4 7.8": ["crasser"], "15.5 10.4 15.5": ["ecto"], "25.1 21.3 8.9": ["batmobile"], "9.5 8.3 9.5": ["exhusband"], "7.5 7.9 8.1": ["chloracne"], "-1.1 10.7 8.8": ["assemblypersons", "extramedullary"], "10.4 -3.1 4.4": ["wdc"], "19.9 8.6 26.9": ["bunless"], "5.7 9.6 0.2": ["polymaths"], "11.9 23.7 3.7": ["formidible"], "7.4 16.5 23.6": ["hamantashen"], "10.7 10.4 4.9": ["infosecurity"], "4.6 8.8 3.3": ["spermicidal"], "8.6 1.6 13.8": ["quando"], "-4.7 13.6 0.8": ["disengagements"], "12.7 7.9 9.7": ["nonplayer"], "1.2 9.1 12.1": ["groundrules"], "-5.8 1.9 1.8": ["sabda"], "7.0 3.0 20.8": ["ramie"], "13.3 7.0 13.5": ["bogart"], "-6.6 15.7 6.7": ["witnessess"], "3.4 9.4 26.5": ["bryostatin"], "9.7 11.1 8.6": ["simulants"], "-3.8 6.1 7.6": ["nonstatutory"], "22.9 11.9 27.5": ["nutshells"], "3.9 16.6 12.6": ["outie"], "7.3 3.7 -1.6": ["liabilites"], "7.0 12.5 6.3": ["whenthey"], "11.2 5.8 18.7": ["namkeen"], "12.9 -1.6 -5.3": ["offerring"], "6.8 12.8 13.0": ["skosh"], "1.4 5.1 4.2": ["transracial"], "12.5 7.7 29.9": ["pizzelles"], "2.8 10.0 13.0": ["anelka"], "-0.4 11.9 22.9": ["mezes"], "9.5 1.7 8.4": ["gladrags"], "5.2 7.9 18.0": ["witbier"], "17.7 4.9 6.9": ["evolutional"], "-0.2 13.9 9.5": ["parliamentarianism"], "16.8 15.6 9.0": ["crashgate"], "3.5 5.1 19.7": ["grassiness"], "2.4 5.3 3.4": ["fineprint"], "4.8 23.6 16.5": ["sightlessness"], "11.9 7.2 7.4": ["custome"], "12.2 11.5 9.3": ["crashy"], "5.0 14.3 1.4": ["overcoached"], "-2.6 10.0 10.6": ["jat"], "2.3 4.3 -6.2": ["serialise"], "14.7 13.1 14.9": ["zodiacal"], "-2.6 11.1 -0.4": ["ostracizes"], "16.7 18.8 11.1": ["perforin"], "5.7 -4.0 1.6": ["convertable"], "5.4 10.3 15.8": ["oxidises"], "0.6 6.1 10.5": ["orthologs"], "3.8 7.4 2.2": ["foreing"], "4.2 11.8 13.0": ["welters"], "0.9 8.9 6.6": ["transpersonal"], "15.0 16.0 16.8": ["rotters"], "12.3 10.8 7.6": ["clockwatch"], "17.9 4.5 4.3": ["bumph"], "14.9 10.1 9.6": ["pocketsize"], "10.2 15.9 10.6": ["ocassional"], "2.4 12.0 7.7": ["plagarism"], "7.3 9.0 18.5": ["brilliants"], "11.2 2.5 17.9": ["zan"], "8.7 13.0 8.3": ["bluejacking"], "17.8 11.7 21.2": ["frolick"], "27.4 19.4 37.9": ["woodlice"], "10.0 14.2 9.7": ["unfeasibility"], "6.0 12.4 8.0": ["juuuust"], "2.3 11.5 10.2": ["disinfections"], "-0.8 2.1 6.8": ["controversal"], "10.2 16.6 21.4": ["butterflys"], "1.1 6.3 4.4": ["dabei"], "10.2 21.0 6.2": ["trigonometric"], "18.8 -3.5 4.0": ["multidistrict"], "9.0 19.6 11.3": ["flamebait"], "6.7 -1.8 11.8": ["whitebook"], "1.5 7.1 7.9": ["fiancie"], "10.2 13.9 5.9": ["guised"], "1.3 16.6 10.3": ["actvities"], "8.0 4.8 13.9": ["artworld"], "13.9 9.8 12.9": ["untrendy"], "8.2 9.2 14.9": ["nack"], "15.4 2.0 8.4": ["sextuple"], "5.5 26.5 17.9": ["stoolie"], "10.6 -1.3 5.3": ["techinical"], "4.4 10.7 16.2": ["outswam"], "-0.9 -1.2 2.4": ["completition"], "12.1 7.5 5.6": ["internatinal"], "1.0 14.1 2.2": ["tramiprosate"], "8.6 1.5 14.7": ["dek"], "10.3 14.9 9.2": ["illigal"], "-2.2 12.2 -0.4": ["jurisdictionally"], "14.7 11.1 6.7": ["slacktivism"], "10.8 -4.2 4.7": ["supersector"], "7.5 6.6 4.7": ["indentifies"], "0.0 2.3 4.6": ["nanocatalysts"], "1.4 8.9 2.2": ["paas"], "17.0 15.1 24.5": ["sumacs"], "7.6 11.6 11.2": ["metavolcanic"], "5.4 23.5 0.4": ["deauthorize"], "9.4 2.9 21.5": ["cucina"], "8.4 3.5 9.5": ["ingles"], "5.3 23.4 5.5": ["exsist"], "14.1 15.7 12.7": ["thowing"], "-7.0 19.4 3.0": ["retaught"], "4.0 2.9 10.4": ["aked"], "2.0 3.4 2.6": ["quadruplex"], "12.6 11.2 46.8": ["yellowbelly"], "4.8 -6.2 4.4": ["fonds"], "27.9 20.0 13.2": ["smartie"], "-0.2 9.4 -1.1": ["rewriter"], "-0.8 6.5 26.3": ["kesar"], "3.3 2.5 5.4": ["ammeter"], "4.3 5.3 4.3": ["netincome"], "-1.9 17.2 1.1": ["principlists"], "6.4 4.8 4.8": ["successs"], "-9.5 18.9 3.9": ["contextualisation"], "4.9 -0.7 11.8": ["auricular"], "-5.4 12.2 3.5": ["mohallas"], "11.2 6.3 32.0": ["swiftlet"], "3.5 9.3 0.9": ["finacially"], "5.6 3.1 6.8": ["nio"], "9.7 -0.3 -2.1": ["unseals"], "6.8 5.6 15.5": ["methylamphetamines"], "5.8 -0.1 2.0": ["cyclodextrins"], "11.3 6.6 5.1": ["populaire"], "0.6 4.9 8.6": ["verbatims"], "7.2 21.5 10.7": ["perimiter"], "11.4 13.1 14.8": ["swifty"], "5.6 14.8 11.6": ["dishdashas"], "5.9 1.8 4.1": ["quiere"], "14.4 2.8 24.9": ["fresca"], "3.0 2.7 -1.1": ["histo"], "4.0 5.7 10.9": ["newby"], "8.3 3.2 15.7": ["verrrry"], "11.4 14.6 28.7": ["towhee"], "14.2 13.0 9.5": ["albiceleste"], "4.6 5.1 5.3": ["unrested"], "2.6 6.2 16.3": ["bennett"], "21.0 11.1 21.7": ["catamount"], "2.0 3.5 10.3": ["flowergirl"], "-4.4 3.4 9.1": ["sulfonamides"], "8.2 -2.5 14.8": ["tarde"], "10.4 11.0 14.5": ["biofortification"], "11.7 21.5 10.3": ["lich"], "7.3 3.1 18.0": ["endosulphan"], "-1.5 10.3 4.4": ["limite"], "8.2 4.2 15.6": ["handwraps"], "-5.6 2.8 21.2": ["secco"], "10.5 10.2 30.9": ["weisswurst"], "9.1 10.1 12.1": ["fromn"], "15.6 13.5 1.7": ["tattletales"], "8.7 16.1 9.9": ["ambulating"], "-1.8 9.2 12.5": ["farceur"], "-1.4 12.4 4.4": ["rigorousness"], "-6.0 7.2 3.8": ["unremedied"], "8.5 10.7 8.3": ["fustian"], "29.3 7.7 19.4": ["clackers"], "2.0 7.6 5.7": ["mugham"], "5.9 0.7 28.5": ["kao"], "28.2 1.7 13.3": ["glitterball"], "20.4 16.1 15.2": ["livelong"], "12.4 5.5 18.9": ["quanto"], "15.9 9.9 6.5": ["communciations"], "15.8 2.8 35.2": ["brunoise"], "9.5 14.7 4.3": ["sado"], "12.1 1.1 -1.2": ["whichhas"], "15.4 10.9 13.5": ["gizmodo"], "-11.9 1.5 2.8": ["distirct"], "0.3 5.7 2.3": ["thermostable"], "9.5 4.2 18.4": ["yardman"], "10.9 4.8 21.4": ["aromatically"], "19.7 4.2 15.2": ["knackery"], "16.7 -5.6 5.7": ["multicrore"], "2.8 -1.4 13.0": ["arall"], "-3.4 6.2 7.0": ["permalinks"], "3.2 -6.6 6.8": ["communautaire"], "-3.3 14.7 -1.5": ["assigment"], "4.6 7.7 6.7": ["harold"], "6.2 17.3 8.3": ["disjointedly"], "5.3 3.3 4.8": ["freshmeat"], "2.7 4.7 15.8": ["reynolds"], "20.2 28.5 5.7": ["witlessly"], "6.7 6.1 27.1": ["bianca"], "6.0 11.4 8.9": ["wayto"], "3.0 3.7 25.0": ["bubur"], "-2.3 8.2 5.6": ["hyperoxia"], "4.0 8.6 6.0": ["declarable"], "12.6 10.7 18.9": ["bushie"], "-5.9 15.5 5.4": ["patellofemoral"], "7.6 9.8 5.0": ["tambura"], "6.0 -4.4 10.4": ["heng"], "2.6 12.8 8.6": ["vehilce"], "0.6 12.2 3.0": ["suffereing"], "2.9 27.0 -1.4": ["exfiltrate"], "3.4 12.1 4.2": ["developmentalist"], "16.0 5.5 16.8": ["samovars"], "13.7 0.6 7.9": ["honkytonks"], "14.6 7.6 17.9": ["surfable"], "-6.6 0.5 3.0": ["redrafts"], "-1.8 11.3 0.0": ["hypothec"], "-0.1 7.2 3.7": ["heterostructures"], "3.7 5.1 12.3": ["elates"], "2.0 11.9 9.9": ["sahi"], "-6.9 -4.0 1.3": ["microamperes"], "-0.3 2.0 0.8": ["puis"], "0.9 0.2 4.5": ["pemoline"], "-2.5 8.1 2.3": ["compendious"], "9.1 8.3 31.7": ["pitmasters"], "12.9 24.4 21.9": ["enzugiri"], "0.5 1.8 5.0": ["ofnew"], "0.7 5.6 6.9": ["cellcontrol"], "-7.0 12.6 2.6": ["dded"], "22.0 5.3 8.0": ["wallchart"], "12.2 21.6 9.1": ["thralls"], "12.0 13.0 7.4": ["unpropitious"], "7.9 7.5 5.5": ["lamplighters"], "13.3 0.1 12.7": ["bassinette"], "6.9 8.4 13.1": ["nanoreporters"], "10.1 7.8 12.4": ["sequelitis"], "19.6 8.8 12.4": ["benjamins"], "14.3 2.7 0.6": ["towin"], "-10.9 -1.5 2.7": ["diplomates"], "5.7 6.3 13.9": ["bluestocking"], "10.5 2.6 -5.8": ["secunet"], "14.7 4.9 -5.7": ["radiopharmacy"], "15.1 -6.5 -0.1": ["eerste"], "16.5 7.2 9.9": ["mihrab"], "2.7 4.8 11.9": ["microemboli"], "16.6 19.8 2.2": ["startegy"], "10.7 14.6 13.2": ["northeastwards"], "5.2 12.6 4.7": ["nanoliter"], "7.1 5.0 5.1": ["toreduce"], "11.9 -3.7 15.5": ["botanica"], "0.7 6.8 11.5": ["endonuclease"], "10.9 10.2 33.3": ["electroshocking"], "-2.3 8.9 2.3": ["seroma"], "-5.7 -0.8 1.1": ["ropivacaine"], "16.6 10.0 40.3": ["sika"], "6.7 8.1 17.8": ["concentrically"], "2.3 11.0 12.5": ["param"], "7.5 10.7 11.8": ["alte"], "12.5 0.8 8.3": ["ultracracker"], "-2.9 -0.4 9.3": ["kes"], "-2.5 1.8 -1.3": ["showcaused"], "6.7 11.1 0.9": ["unfollowed"], "18.1 19.6 21.0": ["burring"], "10.2 2.2 10.9": ["throwball"], "0.6 16.7 8.3": ["elinor"], "24.1 23.6 32.8": ["bluebottle"], "2.0 15.5 5.3": ["quesiton"], "-11.6 -0.4 -4.1": ["proofreads"], "3.9 3.2 8.6": ["abbott"], "10.1 29.9 9.5": ["escaper"], "-5.5 -0.1 9.7": ["nonrelatives"], "5.7 2.0 9.8": ["permited"], "12.5 17.2 18.0": ["swanton"], "7.6 -0.0 16.7": ["duotone"], "6.4 16.0 8.4": ["nonexperts"], "4.5 12.1 5.9": ["tumhara"], "6.4 9.0 -3.6": ["tofind"], "8.6 7.6 11.6": ["guillotining"], "12.6 2.8 5.3": ["plaqued"], "0.8 21.7 -4.1": ["disaccord"], "3.5 14.9 9.7": ["abstractness"], "8.0 10.4 10.2": ["descaling"], "9.7 3.0 11.8": ["compu"], "5.4 31.6 8.9": ["ethnocracy"], "-6.5 13.8 6.0": ["popularizers"], "9.7 4.2 17.5": ["prezzies"], "2.5 5.4 -4.9": ["aknowledged"], "3.2 19.2 -0.5": ["regroupment"], "4.6 4.2 11.5": ["soundwalls"], "-3.5 8.5 14.1": ["carignan"], "-1.7 2.2 -0.8": ["orthopaedists"], "-2.0 8.8 5.7": ["cohabits"], "7.6 10.7 10.0": ["pedalboard"], "2.6 5.7 23.6": ["taiji"], "-2.0 10.3 2.3": ["cirrhotic"], "18.5 16.2 18.3": ["lycanthropic"], "-11.1 2.7 11.2": ["fannings"], "-0.8 3.0 0.0": ["oner"], "3.5 4.7 15.8": ["capelets"], "13.7 20.9 11.4": ["goldbugs"], "2.8 8.0 7.8": ["megillah"], "5.8 -0.4 5.7": ["maxxed"], "0.9 13.3 1.4": ["disserved"], "10.5 4.2 47.2": ["gafftop"], "15.1 -1.2 10.4": ["interestin"], "12.9 21.9 1.0": ["firebombers"], "0.9 2.7 14.2": ["sured"], "7.5 2.3 10.1": ["cardlock"], "8.9 25.4 16.6": ["newbs"], "11.3 4.8 28.9": ["cavy"], "14.7 -4.3 13.6": ["warehousemen"], "-3.5 10.0 1.0": ["clubmakers"], "0.7 17.0 7.7": ["omnisexual"], "-1.4 -4.6 -3.4": ["iscurrently"], "20.4 -7.0 -0.4": ["puchased"], "5.7 4.5 8.6": ["fw"], "6.1 7.7 4.4": ["dancemaker"], "-0.1 17.1 -0.9": ["sufis"], "8.8 2.6 16.5": ["jodhpur"], "14.5 8.5 6.3": ["trailors"], "-7.4 -7.0 0.1": ["transapical"], "7.1 9.2 15.7": ["skywatching"], "-0.0 7.6 25.8": ["sailboards"], "3.4 2.1 12.4": ["milkshaking"], "10.6 6.2 11.2": ["perkiest"], "2.8 12.1 9.0": ["bioaccumulative"], "12.4 -1.9 9.7": ["southend"], "12.3 9.1 11.4": ["reclose"], "2.5 0.9 2.8": ["mutagenicity"], "11.9 13.6 6.8": ["dictats"], "11.4 7.5 21.6": ["railbird"], "6.5 8.9 22.9": ["boto"], "8.2 21.2 7.3": ["dissembler"], "5.4 8.4 5.4": ["powersport"], "5.6 31.8 8.7": ["hench"], "0.8 18.2 18.7": ["copulations"], "-0.2 8.4 12.6": ["erythematous"], "11.4 19.7 4.8": ["constructible"], "6.7 20.2 9.6": ["outcaste"], "-1.0 4.4 6.0": ["booklists"], "0.4 0.3 21.0": ["saxitoxin"], "-0.4 17.1 5.1": ["overinterpret"], "8.4 7.1 31.4": ["rivermouth"], "19.4 13.3 24.0": ["pointier"], "6.2 -0.5 34.4": ["chicharron"], "9.5 -0.3 29.8": ["grissini"], "9.3 8.8 24.9": ["cyclos"], "12.3 13.2 11.5": ["hyperactively"], "10.5 -3.5 4.8": ["bioscientists"], "5.3 5.2 6.6": ["webster"], "10.4 1.2 7.6": ["verte"], "-8.4 6.3 10.9": ["bodyworkers"], "6.5 0.6 5.0": ["incease"], "9.9 8.9 12.6": ["bedcover"], "14.0 6.2 4.8": ["cossetted"], "22.1 8.3 25.9": ["quetzal"], "7.3 8.9 21.4": ["snowmobiled"], "2.8 9.0 4.1": ["appose"], "12.3 7.6 12.6": ["underlays"], "10.7 2.5 9.7": ["fulled"], "2.9 -3.3 18.6": ["excursionists"], "4.8 6.5 20.1": ["carferry"], "-2.6 7.0 10.0": ["labral"], "6.8 10.2 9.2": ["liveness"], "13.6 5.3 13.3": ["tealights"], "14.0 2.4 33.8": ["parma"], "0.7 9.5 11.7": ["bengali"], "4.0 17.0 2.5": ["presumptious"], "1.9 3.4 37.2": ["hito"], "-5.5 7.9 9.7": ["marrige"], "8.9 7.2 8.4": ["integrateds"], "2.4 1.8 11.7": ["snowcross"], "14.7 17.6 9.8": ["grifting"], "7.7 11.8 29.3": ["catboat"], "13.5 6.5 11.0": ["compaired"], "22.1 12.0 38.4": ["gigas"], "17.8 13.3 15.1": ["churners"], "-4.9 12.8 3.6": ["subdivider"], "12.1 20.6 19.3": ["colourblind"], "13.0 27.0 20.4": ["devas"], "8.8 6.5 11.5": ["casas"], "4.8 -6.0 12.8": ["aone"], "13.4 19.0 12.3": ["pssst"], "8.0 -2.3 12.8": ["forcasted"], "5.2 6.9 -0.3": ["indigenised"], "2.4 28.4 6.4": ["annihilations"], "9.1 1.6 21.5": ["liquer"], "2.1 11.5 17.0": ["poesy"], "16.2 9.8 19.3": ["waterworld"], "-1.3 7.2 1.4": ["torr"], "4.4 17.5 8.8": ["relearns"], "8.4 4.3 1.6": ["cme"], "1.2 3.5 4.1": ["efit"], "7.0 7.2 1.7": ["cerebration"], "3.0 26.7 -2.1": ["gitmo"], "13.3 4.6 10.2": ["aslant"], "4.9 13.3 15.9": ["midtones"], "16.0 11.1 18.4": ["cryptozoologist"], "5.6 -0.6 10.6": ["cael"], "16.9 10.8 -0.1": ["biogenetics"], "11.9 15.4 19.5": ["roda"], "-6.0 2.6 1.3": ["enewsletters"], "1.1 8.0 20.3": ["roxarsone"], "8.6 8.2 9.3": ["depeg"], "13.2 3.0 42.0": ["sunchoke"], "5.3 1.2 13.5": ["piezoceramic"], "11.4 9.8 31.9": ["heronry"], "-4.0 6.2 -3.0": ["impleading"], "5.6 -1.5 1.0": ["subpoened"], "8.6 10.8 18.5": ["midspring"], "11.0 33.5 17.4": ["reinvasion"], "10.9 3.1 20.7": ["karoke"], "0.0 4.6 13.0": ["barat"], "2.1 -1.1 5.4": ["marr"], "3.8 3.9 8.2": ["veut"], "11.5 14.0 14.9": ["microvilli"], "10.3 8.9 8.6": ["pluto"], "5.6 -2.4 21.9": ["pha"], "19.1 13.8 19.5": ["crayoned"], "0.2 11.4 12.2": ["poeticism"], "8.9 16.8 9.0": ["compressional"], "8.7 6.4 20.2": ["tubercle", "sylvestris"], "11.5 14.0 9.4": ["helment"], "18.3 22.5 35.6": ["hoverflies"], "20.6 6.6 20.5": ["icious"], "1.0 4.5 3.5": ["prepayable"], "5.2 20.1 5.0": ["deflective"], "5.8 1.3 8.1": ["carnatic"], "6.1 10.9 8.5": ["microvessels"], "3.8 25.2 6.1": ["wronger"], "7.0 8.1 11.9": ["caffeinate"], "5.9 17.6 4.2": ["turbanned"], "10.4 11.1 9.3": ["ordinate"], "17.7 15.8 12.5": ["adventured"], "5.2 10.4 2.1": ["adavantage"], "6.0 3.8 10.3": ["shandies"], "13.1 6.0 20.7": ["benjamin"], "4.3 11.8 13.1": ["nonscientist"], "21.7 2.0 6.0": ["lagger"], "0.5 1.4 10.7": ["icefloe"], "8.2 -2.4 12.5": ["polydactyly"], "-1.4 2.7 5.2": ["disponible"], "-5.5 18.2 -4.7": ["laic"], "9.1 6.9 36.6": ["damsons"], "4.4 5.0 14.1": ["korte"], "10.9 14.7 15.5": ["cumming"], "4.6 10.3 17.8": ["littermate"], "7.3 8.8 11.8": ["microformat"], "-5.1 7.2 8.2": ["osmolality"], "2.8 -3.9 3.8": ["danceline"], "8.4 20.5 6.3": ["antiriot"], "15.0 25.8 24.6": ["hootch"], "-1.9 11.6 8.6": ["brickbatting"], "16.2 0.8 15.0": ["ogee"], "-6.9 4.4 6.9": ["hostelling"], "4.2 13.7 11.2": ["knockings"], "21.3 2.4 9.6": ["billiion"], "18.7 11.1 30.9": ["rumped"], "6.2 7.2 8.9": ["hammertoe"], "17.5 3.2 17.2": ["archeopteryx"], "5.5 10.3 11.9": ["pawl"], "3.2 1.4 4.5": ["memoria"], "2.5 0.5 14.7": ["periosteal"], "5.3 8.3 3.3": ["ordre"], "8.8 5.5 11.1": ["bui"], "1.0 8.9 3.2": ["demande"], "2.1 6.4 10.6": ["pushier"], "8.9 2.9 10.8": ["costumery"], "5.2 5.4 4.1": ["intitially"], "10.1 2.6 10.1": ["regasify"], "5.9 25.7 22.2": ["rootworms"], "14.4 15.5 28.4": ["depthfinder"], "16.9 9.7 14.0": ["fumagillin"], "10.5 9.2 1.0": ["copybooks"], "18.2 28.4 22.4": ["battlement"], "5.7 1.4 4.5": ["vont"], "-6.2 9.0 14.7": ["erry"], "-14.8 5.2 2.0": ["nondisciplinary"], "5.7 13.8 4.8": ["lumefantrine"], "-6.8 15.5 5.8": ["unifications"], "14.8 24.2 19.1": ["tomcats"], "3.5 -1.2 16.8": ["secondo"], "8.2 6.2 22.3": ["perfumey"], "6.7 30.5 7.8": ["unknowables"], "22.4 7.4 14.5": ["supercheap"], "17.7 4.7 27.2": ["shedder"], "11.7 16.4 17.6": ["druidic"], "9.8 13.4 13.6": ["sweatiness"], "14.6 27.7 12.7": ["limitlessness"], "9.3 12.0 7.4": ["defib"], "-0.1 -6.1 8.4": ["aht"], "1.6 9.4 2.9": ["avalable"], "8.3 15.2 11.4": ["buraku"], "-3.5 1.8 8.9": ["pancreatectomy"], "3.7 13.9 3.3": ["valuble"], "4.1 12.9 23.9": ["ryes"], "3.7 18.4 10.7": ["glufosinate"], "13.0 10.3 14.1": ["offf"], "-3.9 7.9 3.3": ["tetrachloroethene"], "20.6 13.7 6.3": ["visored"], "3.1 16.0 10.9": ["maddy"], "9.0 3.9 10.9": ["wangling"], "11.3 6.6 25.6": ["bhel"], "5.4 8.4 6.9": ["societys"], "10.9 16.9 3.9": ["unflawed"], "-0.7 5.0 -4.2": ["deboarded"], "9.0 10.9 4.0": ["economiesuisse"], "17.6 10.4 12.1": ["ekeing"], "-4.3 12.5 6.6": ["impactive"], "-3.7 -0.2 -2.1": ["pbviews"], "3.4 1.5 2.2": ["earfuls"], "11.5 -0.1 12.8": ["pasteurizer"], "3.2 12.4 6.5": ["efforting"], "10.8 5.1 9.0": ["yessir"], "3.0 5.4 13.0": ["nubbed"], "-3.3 18.6 4.4": ["vigilent"], "4.6 5.6 4.0": ["barmitzvah"], "12.1 12.1 18.6": ["drillpipe"], "0.9 11.4 3.4": ["politik"], "5.4 7.7 7.1": ["mundi"], "8.0 17.2 12.2": ["strokeplayers"], "6.2 -6.7 10.6": ["maes"], "1.3 -4.2 -1.6": ["visite"], "-0.2 -12.0 1.7": ["accredition"], "1.4 5.6 18.4": ["silicomanganese"], "9.7 5.6 11.7": ["adelaide"], "2.4 12.5 -0.5": ["diasporans"], "4.7 12.9 9.6": ["regedit"], "2.7 6.1 19.4": ["hypogene"], "16.9 12.6 29.8": ["swimmin"], "5.2 7.1 6.7": ["klein"], "-7.0 -3.5 -0.7": ["reccomendation"], "-1.2 6.4 -2.1": ["centenaries"], "-3.3 12.5 8.5": ["thiocyanate"], "0.6 8.2 6.7": ["tariffing"], "12.3 2.2 23.5": ["candlemaking"], "12.4 5.9 -0.1": ["tobring"], "5.0 8.7 27.7": ["soto"], "20.8 8.9 11.5": ["wackily"], "8.3 25.8 8.9": ["shotty"], "-3.7 6.3 3.4": ["thorpe"], "19.6 11.0 13.7": ["frau"], "5.6 19.9 4.5": ["posessed"], "-1.0 3.0 8.6": ["clubfeet"], "9.1 1.6 10.2": ["celebrites"], "9.6 9.3 27.9": ["meadowfoam"], "11.4 5.7 11.3": ["bannisters"], "2.6 8.1 -0.1": ["piont"], "10.7 17.9 14.1": ["gaman"], "13.0 22.0 4.0": ["revealer"], "5.0 5.2 6.0": ["myocyte"], "22.4 10.7 17.6": ["wallrides"], "9.1 23.6 8.7": ["satrapy"], "11.0 22.6 13.3": ["flailings"], "3.0 16.8 8.3": ["themseleves"], "19.5 5.0 18.9": ["wellie"], "13.7 18.5 10.1": ["semtex"], "17.9 11.3 22.8": ["scilla"], "1.4 7.2 -1.0": ["recive"], "8.4 3.8 12.3": ["raya"], "9.6 7.2 23.5": ["pluot"], "2.2 18.7 4.1": ["overinvesting"], "3.5 11.3 4.4": ["confederacies"], "-2.3 5.5 15.1": ["tambons"], "5.5 14.1 20.1": ["countin"], "5.5 8.9 13.3": ["longrun"], "0.2 0.7 3.9": ["waterfloods"], "12.2 22.3 11.3": ["backswings"], "4.2 12.9 10.5": ["kasbah"], "13.2 21.6 15.9": ["sisu"], "20.5 4.8 -0.6": ["ladden"], "18.2 15.8 18.0": ["gasm"], "7.1 3.6 8.4": ["tourdates"], "8.5 -0.6 15.5": ["loro"], "22.2 9.9 21.4": ["beachhouse"], "7.7 9.6 15.0": ["phool"], "5.0 -2.8 1.9": ["cashbacks"], "-2.6 4.6 6.5": ["dilators"], "7.5 18.6 5.8": ["fulcrums"], "0.3 12.7 9.8": ["metaphysician"], "4.8 5.1 11.8": ["sullivan"], "-2.6 -2.9 4.6": ["propafenone"], "5.5 4.4 6.9": ["neurofibromas"], "10.1 4.9 0.5": ["reelstands"], "2.1 3.3 12.5": ["oxyntomodulin"], "16.7 29.6 12.9": ["sidescrolling"], "-1.9 11.2 18.0": ["ulo"], "4.6 10.6 5.1": ["renmimbi"], "5.8 2.3 10.7": ["moteliers"], "4.2 3.5 5.3": ["eec"], "1.4 17.0 11.1": ["reinforcers"], "5.1 9.0 16.9": ["skintone"], "7.9 10.3 15.7": ["backyarders"], "10.8 11.9 11.4": ["blings"], "3.3 6.8 4.6": ["tournamnet"], "11.8 13.5 8.5": ["bodge"], "10.5 -3.4 10.1": ["strikebound"], "-1.6 5.9 -0.0": ["intubating"], "9.5 15.8 10.1": ["reweave"], "18.2 0.9 32.5": ["chorizos"], "5.0 13.8 17.1": ["salvagable"], "12.3 11.9 8.3": ["reformulates"], "5.9 23.4 7.7": ["dumbfounds"], "8.5 18.1 11.4": ["keepings"], "-2.9 -2.4 7.4": ["cirriculum"], "8.3 -0.4 13.3": ["pyrolytic"], "15.4 6.0 11.0": ["resplendence"], "2.0 1.5 2.3": ["lled"], "1.4 17.3 4.7": ["cooption"], "6.8 6.5 13.6": ["acouple"], "19.9 7.7 8.3": ["landesbank"], "2.3 20.0 0.8": ["embeddedness"], "5.0 2.1 2.4": ["reqs"], "7.9 6.5 7.5": ["mocumentary"], "-1.0 1.5 11.6": ["monozygotic"], "5.2 12.2 -1.2": ["intermeshed"], "17.3 -0.1 18.0": ["wobblier"], "-6.9 3.5 -0.8": ["honoraries"], "2.7 -0.9 25.3": ["greenmarkets"], "12.9 26.2 13.0": ["slobberknocker"], "20.0 4.4 15.7": ["unshowered"], "6.8 2.7 -5.0": ["wondertouch"], "-1.8 -1.1 9.0": ["methodist"], "20.0 18.4 12.8": ["ferromagnets"], "9.3 19.0 12.5": ["outfighting"], "-1.2 13.2 7.7": ["unreactive"], "9.5 12.5 12.1": ["sidehill"], "23.6 32.3 15.4": ["raygun"], "-8.5 10.2 5.4": ["describers"], "16.3 30.0 12.3": ["hegemons"], "-1.4 13.2 18.4": ["aroha"], "-0.3 5.0 4.0": ["immunoblotting"], "10.4 12.0 6.3": ["chatbot"], "-3.5 3.1 14.1": ["bailor"], "3.3 8.5 12.8": ["mous"], "-7.2 -2.0 1.3": ["ministerium"], "13.4 10.7 16.7": ["flabbier"], "4.6 20.3 5.8": ["fettering"], "12.8 18.7 16.9": ["punier"], "4.1 8.7 4.0": ["precint"], "-1.7 5.7 9.0": ["chemigation"], "10.4 1.0 2.1": ["gallivanted"], "20.8 7.6 13.8": ["judders"], "8.5 11.1 17.2": ["kumo"], "13.1 7.7 10.5": ["thangka"], "-1.0 -0.5 3.9": ["grayboxx"], "-5.7 11.5 3.7": ["thymoma"], "7.2 6.6 5.8": ["meeters"], "-0.4 4.9 6.5": ["earlybirds"], "5.1 12.8 6.6": ["repartitioning"], "15.1 5.1 14.6": ["kidult"], "22.0 5.3 17.5": ["fruiterer"], "1.1 -5.3 10.6": ["bydd"], "7.1 -6.8 10.6": ["chairback"], "16.1 8.3 36.9": ["scutes"], "15.1 19.0 18.8": ["posey"], "2.8 12.6 13.3": ["subnetworks"], "7.9 8.0 9.9": ["morte"], "-1.5 4.4 2.2": ["incresed"], "17.2 4.4 16.1": ["spindled"], "3.7 12.9 9.0": ["systematise"], "11.7 8.9 13.1": ["porticoes"], "21.2 13.4 27.9": ["unmelted"], "9.9 2.7 -3.9": ["mufin"], "-2.0 1.1 -2.5": ["beclomethasone"], "7.2 12.2 18.7": ["octahedral"], "6.7 10.6 15.7": ["wishin"], "4.9 10.8 6.7": ["rwd"], "0.4 4.5 7.9": ["freeagent"], "8.8 6.3 9.2": ["breaktime"], "1.1 4.2 6.6": ["mohan"], "12.5 5.4 4.1": ["gratuit"], "10.5 5.6 9.9": ["santur"], "-4.3 13.7 4.9": ["endoxifen"], "-6.5 -6.0 -2.6": ["appoinment"], "3.1 3.0 0.2": ["anniverary"], "7.2 -2.5 7.6": ["biocatalytic"], "-0.2 7.5 16.0": ["kayong"], "4.5 12.9 11.0": ["tallis"], "18.2 8.9 9.5": ["armlets"], "20.1 20.3 30.9": ["mainmast"], "6.5 21.2 1.3": ["serjeant"], "0.3 1.8 5.3": ["haemochromatosis"], "1.7 4.9 6.0": ["noscapine"], "-0.4 21.2 2.9": ["misogynous"], "23.3 11.9 12.4": ["alp"], "7.6 17.4 8.8": ["odi"], "10.4 24.1 6.9": ["crimelord"], "1.9 19.9 8.8": ["hypocenter"], "3.1 16.6 14.0": ["overpursued"], "4.2 3.6 5.8": ["multiclass"], "11.4 0.1 4.9": ["relabelling"], "-1.6 3.4 20.2": ["louise"], "-1.5 -2.3 14.6": ["limnologist"], "14.5 11.6 5.3": ["polyphase"], "-2.5 9.0 5.8": ["prothrombotic"], "3.7 11.9 15.1": ["aneuploid"], "5.6 7.3 8.1": ["acyl"], "10.2 -8.4 8.0": ["reve"], "16.4 6.8 7.4": ["guttered"], "-2.1 15.2 10.8": ["casue"], "14.4 -2.0 -5.2": ["affliate"], "-3.1 3.1 6.0": ["ield"], "4.5 4.4 10.2": ["tsm"], "18.7 20.9 13.7": ["wetware"], "8.2 19.7 10.8": ["thearea"], "-4.3 2.7 3.9": ["tahsildars"], "17.1 16.6 22.1": ["stoppered"], "15.6 15.0 17.9": ["cagoule"], "8.5 8.7 13.8": ["micheal"], "-5.5 8.3 6.8": ["reamins"], "1.2 10.3 11.1": ["waaaaaaay"], "7.9 15.1 7.8": ["aquaintances"], "10.1 16.4 11.7": ["bhoot"], "11.5 5.2 0.6": ["subsquently"], "9.8 -2.6 0.6": ["leathergoods"], "5.0 28.6 4.2": ["miltiary"], "-0.9 4.5 4.2": ["anticlotting"], "9.6 11.1 24.7": ["daffs"], "11.3 11.0 20.9": ["gouty"], "14.0 8.0 22.8": ["davit"], "5.8 8.9 17.1": ["tourgoers"], "11.4 15.1 21.6": ["shawty"], "9.2 17.3 6.3": ["batsuit"], "8.2 15.5 14.1": ["psychogeography"], "6.9 8.7 24.1": ["rosea"], "-5.2 -2.8 5.4": ["finweight"], "7.2 -3.5 4.1": ["feedthrough"], "5.0 1.9 1.8": ["colorimetry"], "-5.5 2.7 7.7": ["indapamide"], "1.6 6.9 11.4": ["zar"], "6.2 6.8 18.3": ["clathrin"], "3.9 10.3 9.5": ["tani"], "1.7 23.3 1.1": ["disserve"], "6.2 0.8 4.5": ["percentin"], "0.7 0.4 2.1": ["cerivastatin"], "23.1 6.9 22.8": ["dungaree"], "6.3 4.5 6.7": ["xr"], "-6.6 -3.7 12.1": ["winemaster"], "22.5 5.3 28.2": ["marshmallowy"], "-1.4 4.3 10.0": ["incisional"], "11.5 1.4 21.6": ["tuns"], "-3.1 2.7 7.1": ["superintendants"], "6.3 18.0 12.2": ["fuzzers"], "3.6 7.6 7.2": ["vestries"], "6.6 7.4 14.9": ["thobe"], "13.5 2.9 5.0": ["buildling"], "9.0 16.5 9.5": ["hvae"], "0.3 0.4 4.1": ["personnes"], "11.6 14.1 6.0": ["operant"], "6.8 21.9 14.7": ["sideward"], "5.0 3.9 14.8": ["gho"], "13.7 3.8 10.5": ["chicer"], "1.5 3.6 10.8": ["daytona"], "4.9 5.7 -4.8": ["teratogenicity"], "0.6 3.8 3.7": ["cowriting"], "-0.3 7.1 -6.9": ["conferece"], "1.9 29.2 6.7": ["countersurveillance"], "2.2 11.8 4.6": ["dalal"], "10.3 1.8 0.6": ["theatrette"], "5.0 13.1 18.9": ["epigenomic"], "9.9 -7.5 10.1": ["chairty"], "11.4 10.1 3.6": ["crankcases"], "6.8 2.6 14.7": ["lish"], "13.2 7.4 4.2": ["vw"], "-1.2 3.9 3.1": ["respon"], "17.5 27.7 4.4": ["tinhorn"], "15.8 4.4 9.7": ["flatcar"], "15.6 8.2 31.5": ["bastes"], "13.4 9.1 16.4": ["signet"], "-1.8 -1.1 -6.0": ["questionned"], "0.6 3.8 -4.8": ["inparticular"], "-6.2 19.0 -0.2": ["impartation"], "17.2 7.8 17.2": ["surfie"], "0.9 7.1 8.4": ["anxiolytics"], "4.6 11.2 12.6": ["happenstances"], "5.3 16.1 7.4": ["thast"], "3.1 4.4 -0.8": ["immed"], "9.0 13.2 13.0": ["dunkfest"], "11.6 8.7 21.0": ["tarns"], "8.7 16.0 3.8": ["posssible"], "12.1 14.8 14.2": ["warchests"], "18.4 19.9 15.0": ["collossal"], "10.9 21.2 24.5": ["battened"], "-0.5 2.8 2.8": ["solemnising"], "7.2 18.5 10.0": ["overreactive"], "-5.5 5.5 8.8": ["denaturation"], "-3.3 9.9 13.3": ["mangyari"], "15.6 8.4 22.2": ["cheroot"], "10.2 -6.0 7.4": ["decaliters"], "5.7 4.0 13.7": ["vegoil"], "3.5 23.5 7.2": ["repressiveness"], "6.1 5.1 24.9": ["baon"], "13.1 4.1 21.2": ["flatboats"], "6.5 5.5 11.7": ["vara"], "12.9 5.3 1.2": ["minstry"], "19.7 6.2 16.9": ["flittered"], "4.2 6.3 4.3": ["ferroelectrics"], "9.3 24.5 9.0": ["placation"], "-1.6 1.8 8.9": ["nees"], "6.4 11.1 10.8": ["suhoor"], "10.3 20.1 13.2": ["alarums"], "18.5 15.2 11.0": ["yearningly"], "6.3 3.9 2.8": ["journeywoman"], "7.8 10.2 20.2": ["lidos"], "11.8 -1.5 1.4": ["eos"], "8.9 -3.7 1.9": ["atotal"], "4.4 16.6 7.5": ["apalled"], "10.9 7.8 9.2": ["stretchability"], "5.1 8.7 9.0": ["mexicano"], "5.3 7.4 9.9": ["eget"], "-0.1 2.5 6.5": ["deferasirox"], "-3.3 9.0 6.8": ["tzedaka"], "16.0 4.5 18.2": ["fountainheads"], "7.4 16.8 5.9": ["valences"], "2.9 13.5 9.9": ["cleartext"], "-0.2 10.2 3.5": ["sensative"], "10.0 15.1 33.4": ["ovenbird"], "6.2 15.6 11.1": ["clinger"], "4.8 14.2 11.6": ["wackjob"], "5.9 6.3 25.7": ["nitrofuran"], "10.6 7.7 9.7": ["sunnily"], "8.5 5.1 9.2": ["hyperechoic"], "-0.1 15.3 6.6": ["fanship"], "-0.6 17.4 4.6": ["fragmentations"], "3.9 2.4 3.3": ["xda"], "7.3 -1.8 -4.2": ["telebanking"], "11.6 8.9 13.4": ["conceptualists"], "2.6 31.3 12.1": ["killstreaks"], "9.1 14.4 18.0": ["daintiness"], "2.2 9.1 1.1": ["breathalizer"], "0.2 19.9 5.8": ["rapproachment"], "-4.7 6.5 7.0": ["hygene"], "2.2 5.4 11.4": ["thc"], "12.1 0.6 0.8": ["casio"], "-6.9 2.9 -1.2": ["utilizers"], "-5.1 2.3 13.9": ["tla"], "3.9 5.4 8.9": ["damehood"], "5.5 9.2 12.3": ["ridic"], "14.0 10.9 34.0": ["blintz"], "12.1 3.6 38.6": ["daube"], "-3.3 4.5 9.2": ["pilgrimmage"], "0.5 -5.3 4.8": ["decathlons"], "-5.8 8.0 10.0": ["phaseouts"], "7.1 0.9 6.4": ["segundo"], "15.1 7.4 12.2": ["prc"], "-0.6 23.7 6.9": ["liers"], "6.9 13.8 -1.2": ["situationist"], "9.7 22.8 15.3": ["neigbour"], "-6.8 4.7 6.8": ["zila"], "12.8 14.3 2.8": ["countermovement"], "-4.1 2.7 9.0": ["imbizos"], "3.5 -0.4 9.9": ["varity"], "12.8 17.6 18.6": ["theodolite"], "-5.0 15.2 3.4": ["constituion"], "-3.4 15.2 13.3": ["decendants"], "7.0 1.3 7.9": ["dihydrocodeine"], "-3.6 34.5 1.2": ["fidayeens"], "-2.5 6.6 3.7": ["zeh"], "13.3 12.0 12.8": ["wimmin"], "12.8 4.9 7.8": ["ifying"], "-2.3 11.3 9.2": ["modularize"], "-0.9 5.9 10.7": ["activties"], "-4.3 4.8 -3.1": ["couldnot"], "1.6 11.3 11.5": ["legended"], "7.9 6.7 4.1": ["streetballers"], "-1.4 8.8 0.7": ["reborrowed"], "14.0 9.3 18.3": ["camaro"], "8.7 6.3 9.4": ["zyrtec"], "-2.2 14.2 3.7": ["riyaz"], "-1.0 9.1 7.5": ["excisable"], "5.7 4.3 7.9": ["aage"], "4.5 0.4 14.6": ["italia"], "16.1 5.5 26.9": ["campion"], "-0.9 10.0 -0.1": ["expiratory"], "9.5 16.2 7.0": ["balkanizing"], "2.7 0.8 24.2": ["bayong"], "5.4 5.3 10.6": ["untaxable"], "-8.9 10.4 13.8": ["vivax"], "1.9 -0.9 3.0": ["ouvre"], "19.2 16.9 7.4": ["verticle"], "7.1 18.0 6.4": ["sagaciously"], "9.6 14.3 18.2": ["unthaw"], "-3.0 3.1 3.4": ["fartlek"], "4.2 0.6 8.0": ["cin"], "6.9 19.3 19.5": ["pinewoods"], "-1.0 -1.1 11.9": ["thermosetting"], "7.1 16.2 11.6": ["nucleons"], "8.9 15.7 29.0": ["drosophila"], "8.4 7.9 11.5": ["conomy"], "14.0 3.5 16.0": ["lifestylers"], "2.8 12.7 4.6": ["stringencies"], "16.0 12.3 15.0": ["megastorm"], "10.6 22.5 15.9": ["wussification"], "5.8 6.7 10.4": ["voom"], "7.3 0.7 5.0": ["composable"], "5.1 8.4 11.6": ["baila"], "-0.3 0.0 1.5": ["ote"], "6.2 7.8 9.1": ["antiobesity"], "19.3 13.8 -0.3": ["completey"], "17.6 19.5 25.1": ["icefields"], "3.3 -2.7 8.6": ["prebuy"], "17.8 14.7 18.3": ["pleb"], "13.9 15.2 17.3": ["dangit"], "9.1 3.4 17.0": ["tash"], "-1.0 9.2 4.9": ["champioship"], "-2.1 -2.8 0.6": ["kbs"], "-9.3 13.5 1.5": ["recog"], "-1.0 2.8 -2.1": ["compans"], "6.7 1.5 11.1": ["whiling"], "-4.9 20.4 1.6": ["avoidably"], "-0.4 24.1 4.1": ["lawenforcement"], "2.1 13.5 9.1": ["chenda"], "-3.3 -0.1 7.0": ["singersongwriter"], "14.8 23.0 20.5": ["excremental"], "11.7 11.8 14.9": ["florescence"], "13.3 14.5 34.8": ["omlette"], "23.0 10.3 0.1": ["privatises"], "-0.0 9.0 8.3": ["reblockage"], "9.6 12.6 19.4": ["cellulases"], "11.0 7.8 11.0": ["polyhedral"], "-2.6 11.1 15.9": ["thot"], "15.7 2.0 14.7": ["reticulate"], "-12.0 2.3 1.0": ["nonqualifying"], "16.0 7.3 12.5": ["barrelhead"], "7.5 3.4 -0.5": ["marcomms"], "8.9 10.3 10.4": ["sitelinks"], "1.0 -1.1 20.4": ["manzanilla"], "15.0 17.0 26.9": ["spadix"], "-7.2 6.1 7.7": ["macroalbuminuria"], "5.4 4.1 26.2": ["nitrofurans"], "-2.6 2.1 5.1": ["yearand"], "13.7 19.0 13.6": ["permanantly"], "0.2 22.3 6.5": ["pluralists"], "-1.5 4.7 8.7": ["photocoagulation"], "18.6 1.0 -1.4": ["seel"], "-16.3 9.7 4.9": ["lieves"], "9.4 -4.8 20.8": ["resuspension"], "0.1 4.9 10.1": ["carlo"], "-4.8 17.9 11.6": ["overschedule"], "8.7 11.0 1.5": ["portrayers"], "17.0 9.5 24.7": ["petalled"], "1.7 31.6 5.9": ["armourers"], "1.5 15.3 7.6": ["observationally"], "23.2 8.8 14.7": ["womblike"], "-7.0 7.7 10.7": ["stratifies"], "-2.7 13.5 15.2": ["helminths"], "14.1 2.2 10.8": ["cui"], "3.6 -7.8 10.7": ["rih"], "2.1 7.5 10.6": ["sylvite"], "5.2 21.1 4.8": ["intemperately"], "-6.9 0.8 4.9": ["cyclobenzaprine"], "20.9 27.7 13.7": ["hellscape"], "2.3 12.2 1.6": ["bioenergetic"], "14.8 14.0 19.8": ["whitehead"], "16.1 11.7 18.9": ["lumpish"], "0.6 3.2 11.1": ["rhodes"], "0.3 12.8 7.2": ["leeriness"], "1.4 11.8 10.6": ["preachin"], "17.8 2.8 19.6": ["fluro"], "-2.9 3.4 1.4": ["daijiworld"], "22.7 28.9 14.1": ["hellhounds"], "3.3 8.4 7.6": ["naturalising"], "10.2 4.8 -0.2": ["injunct"], "14.8 8.4 18.6": ["knicknacks"], "4.2 9.2 -7.1": ["indentical"], "2.4 9.3 12.0": ["meine"], "3.2 8.6 10.4": ["wonderings"], "3.5 19.3 10.1": ["azimuths"], "-11.8 11.9 14.4": ["triazoles"], "9.5 8.3 18.6": ["foxtrots"], "-3.3 6.7 6.6": ["cil"], "15.2 23.8 9.7": ["lancers"], "-2.7 15.1 -3.0": ["challanged"], "8.6 8.1 17.0": ["dabbas"], "7.7 33.1 8.5": ["unavenged"], "6.4 32.3 6.5": ["companeros"], "6.9 0.7 5.1": ["stron"], "5.8 9.5 30.8": ["muscadet"], "3.0 16.7 6.0": ["firestation"], "7.6 -0.7 6.7": ["divo"], "4.3 6.5 5.2": ["intramolecular"], "11.5 0.3 21.2": ["cajeta"], "-4.8 -2.3 -2.2": ["cosigning"], "1.7 0.2 15.8": ["agrotourism"], "15.6 11.0 47.4": ["jackfish"], "18.6 7.1 9.0": ["sketchpads"], "3.8 -4.1 6.3": ["millionfor"], "10.5 3.1 14.9": ["asdf"], "-0.5 8.0 24.1": ["culinarian"], "17.7 17.5 -2.7": ["chancellory"], "6.6 11.4 6.5": ["leben"], "3.0 21.6 5.9": ["colombo"], "-0.2 23.3 -3.8": ["securest"], "3.4 5.1 13.7": ["softtabs"], "-1.7 10.8 6.2": ["detering"], "13.7 13.4 12.9": ["hyperrealistic"], "18.0 1.9 17.5": ["phosphogypsum"], "16.0 9.6 23.5": ["repousse"], "1.4 23.3 9.9": ["observably"], "1.5 4.7 1.6": ["stokvels"], "4.3 1.6 11.8": ["boulangeries"], "16.9 25.3 10.0": ["enviroments"], "2.7 14.8 11.2": ["creativities"], "1.7 6.1 8.4": ["ribbie"], "1.0 12.4 8.7": ["wisher"], "5.2 5.4 3.5": ["artsdepot"], "2.7 8.5 -3.7": ["triphendiol"], "8.7 12.1 12.7": ["houseboys"], "-4.3 1.5 11.1": ["agrologist"], "11.9 4.3 -2.1": ["rubberstamps"], "21.5 -1.3 19.6": ["fancypants"], "7.5 7.1 8.9": ["multitracked"], "4.4 14.2 8.3": ["rathyatra"], "-0.7 7.4 11.2": ["repercharge"], "4.6 2.5 5.5": ["notaire"], "15.8 6.8 9.5": ["nickles"], "8.3 2.8 11.4": ["freebsd"], "-1.9 9.2 7.7": ["mohabbat"], "10.1 9.3 31.3": ["crimsons"], "16.5 11.5 10.7": ["brainlessness"], "11.9 25.4 11.2": ["maneouvres"], "10.0 -1.2 3.0": ["developements"], "12.0 0.1 -2.6": ["eading"], "6.2 20.6 2.1": ["medievalists"], "2.2 15.9 8.7": ["officiously"], "8.1 5.1 5.9": ["microdrives"], "8.6 -0.7 9.3": ["unsucessfully"], "0.2 2.9 9.8": ["hypophosphatasia"], "-1.1 -1.7 5.2": ["townshipwide"], "4.9 4.3 14.8": ["kadhi"], "11.6 19.3 8.2": ["tomtom"], "15.6 6.5 8.8": ["micromachined"], "1.5 4.8 21.3": ["oxytetracycline"], "7.5 23.1 13.1": ["gorehounds"], "5.1 14.6 16.8": ["amrit"], "18.0 8.9 26.6": ["cuy"], "4.5 10.2 10.8": ["kuyt"], "10.2 16.5 26.3": ["mout"], "-7.3 4.4 -0.7": ["palyed"], "17.6 3.6 26.1": ["cran"], "8.8 7.7 1.2": ["successul"], "2.5 8.1 21.2": ["rewarmed"], "-1.5 -0.4 9.9": ["housemasters"], "4.4 -6.2 6.7": ["nullnullnull"], "-1.8 -0.3 8.1": ["clinicopathologic"], "6.6 23.7 9.7": ["shamus"], "6.7 21.4 11.6": ["fagged"], "8.3 11.2 8.5": ["cartoonishness"], "2.3 2.0 14.1": ["reso"], "0.9 4.4 12.1": ["lateralization"], "20.5 2.8 26.0": ["duckbill"], "6.9 4.2 27.8": ["booya"], "5.6 -6.6 2.6": ["everal"], "5.5 14.4 -1.1": ["unscholarly"], "10.7 3.5 33.2": ["tatsoi"], "4.9 4.0 12.7": ["dich"], "3.3 25.2 0.2": ["misson"], "5.2 27.8 8.1": ["noninterventionist"], "7.9 -1.1 9.2": ["prada"], "15.0 26.0 11.6": ["overlordship"], "0.0 10.8 -2.8": ["deadheat"], "10.7 -2.6 -3.9": ["andservices"], "11.1 7.3 33.7": ["beurre"], "20.4 6.7 28.3": ["potful"], "9.3 10.1 6.4": ["methylenedioxypyrovalerone"], "17.2 17.8 18.8": ["nutsack"], "7.7 3.6 7.2": ["triax"], "-1.7 9.0 13.1": ["datatypes"], "3.4 3.4 11.5": ["seulement"], "5.7 6.9 27.7": ["matar"], "-5.6 -6.6 4.5": ["mcfgpd"], "11.2 9.3 19.7": ["patissier"], "15.5 2.9 28.1": ["crispiest"], "5.7 27.3 3.1": ["dissembles"], "2.9 20.6 11.3": ["reinforcer"], "2.6 0.5 5.4": ["heb"], "11.0 18.0 6.5": ["paternalistically"], "0.3 9.4 5.8": ["inflammasome"], "-2.1 9.1 2.4": ["ecclesiastics"], "4.0 11.8 9.0": ["reiners"], "28.3 7.6 5.1": ["chainstore"], "13.0 28.2 16.6": ["unfreedom"], "12.3 1.1 22.3": ["cidery"], "6.3 1.6 9.4": ["solderless"], "6.6 14.2 14.6": ["babooph"], "18.7 6.4 8.5": ["utilites"], "19.6 11.7 8.9": ["baloon"], "-10.8 8.9 4.3": ["hawaladars"], "19.8 17.5 6.5": ["unlocker"], "32.0 6.9 24.0": ["beachballs"], "20.0 32.8 18.6": ["camoflage"], "5.1 2.8 6.1": ["assurers"], "-2.4 -2.5 9.1": ["innkeeping"], "-0.3 -4.9 6.2": ["tumultuousness"], "19.9 1.3 4.7": ["headquartering"], "1.6 6.3 7.9": ["unconferences"], "13.9 4.1 31.0": ["honeydews"], "10.4 5.9 17.9": ["housey"], "-3.5 8.5 2.4": ["elacytarabine"], "4.8 16.3 8.1": ["bida"], "5.2 14.0 11.4": ["hammies"], "3.4 -1.7 -2.4": ["fesoterodine"], "5.3 -3.3 4.1": ["avaialable"], "5.9 9.1 14.6": ["tranportation"], "11.5 20.6 9.8": ["fuckup"], "-1.0 3.8 10.0": ["rifabutin"], "9.9 6.2 34.2": ["donair"], "4.0 10.1 13.0": ["volumetrically"], "11.1 23.7 8.8": ["amunition"], "3.2 16.9 2.5": ["abler"], "-1.3 10.6 4.0": ["advatage"], "5.8 8.1 14.6": ["fuerte"], "-0.7 10.4 7.1": ["eda"], "1.9 14.6 4.4": ["looseforward"], "12.2 -7.1 8.7": ["nonbranded"], "6.7 7.3 5.3": ["stalement"], "19.9 5.3 11.6": ["dowm"], "6.8 5.2 11.4": ["courtsquare"], "2.6 0.2 14.8": ["gittin"], "12.6 9.8 26.0": ["caramelise"], "4.4 9.8 12.0": ["discbox"], "10.5 1.7 18.0": ["caverta"], "6.8 1.4 2.8": ["retoucher", "paige"], "9.3 24.1 8.9": ["antagonistically"], "14.0 11.5 1.4": ["imbeds"], "3.3 17.4 0.5": ["islamization"], "14.9 16.4 14.5": ["greaseball"], "3.7 -2.9 7.8": ["exercice"], "1.7 2.7 7.1": ["restages"], "-0.3 5.5 8.5": ["buildability"], "12.7 6.7 10.4": ["manne"], "13.1 7.6 15.3": ["ymca"], "0.4 22.5 6.7": ["legalists"], "11.1 17.3 11.4": ["suspectedly"], "5.6 7.2 20.4": ["lacustrine"], "11.9 12.9 16.1": ["folksonomies"], "-3.8 5.9 12.1": ["magaling"], "6.9 13.6 9.8": ["pollutive"], "12.2 16.3 16.1": ["palpating"], "8.1 9.3 5.7": ["newsmag"], "10.5 17.7 24.5": ["migrators"], "15.2 -2.6 16.9": ["flashboards"], "4.7 1.4 3.1": ["marblemedia"], "7.8 -2.8 3.4": ["refix"], "11.0 3.5 6.8": ["flowstations"], "1.4 28.1 -0.6": ["othering"], "13.8 5.0 30.8": ["spicey"], "8.9 3.3 5.8": ["chondrolysis"], "7.6 0.2 13.0": ["roland"], "2.8 11.8 9.8": ["jejemon"], "13.8 12.4 11.7": ["motorbikers"], "17.4 6.3 3.1": ["busienss"], "14.7 19.0 0.6": ["radiolocation"], "2.5 13.4 18.1": ["quickish"], "1.0 1.6 5.7": ["undoped"], "0.4 2.5 4.9": ["waterflooding"], "7.6 13.7 13.5": ["embouchure"], "17.2 -1.5 25.3": ["snickerdoodle"], "-1.0 1.2 8.8": ["nonpremium"], "7.6 7.2 10.3": ["sawbones"], "-7.4 2.8 -5.4": ["ansd"], "9.3 7.0 10.8": ["directv"], "10.2 16.0 5.5": ["transcendant"], "6.8 2.9 14.6": ["sprintcars"], "-3.2 -0.2 -8.4": ["informtion"], "-3.6 7.9 6.0": ["fahrenheit"], "-6.3 1.2 12.8": ["midspans"], "12.1 7.3 9.5": ["nightshirts"], "4.1 -1.3 9.9": ["prebooked"], "10.6 17.5 18.6": ["bloodsports"], "8.0 14.9 9.0": ["goonery"], "-4.6 -0.1 10.4": ["prevocational"], "3.8 8.2 8.3": ["remarketers"], "12.6 7.7 30.7": ["oden"], "8.5 6.5 5.8": ["kleine"], "7.8 3.2 3.7": ["arcsec"], "6.1 15.8 9.5": ["scandalizes"], "7.8 9.2 46.1": ["pikeminnows"], "7.7 16.1 6.3": ["mouz"], "1.6 6.9 11.8": ["hecho"], "12.7 16.4 12.2": ["arresters"], "16.3 12.4 9.9": ["ishly"], "3.1 13.3 5.9": ["precarity"], "1.2 30.0 -0.2": ["attck"], "4.1 18.9 21.4": ["passin"], "10.2 15.5 8.2": ["aestheticized"], "2.7 3.8 7.5": ["stateswomen"], "15.9 -0.3 23.7": ["icecreams"], "19.4 3.6 14.7": ["mansard"], "11.3 2.0 6.4": ["tappings"], "15.8 9.7 31.7": ["robata"], "10.7 11.1 4.6": ["underdeliver"], "18.1 8.3 18.4": ["skyscapes"], "10.9 21.9 15.3": ["ravishes"], "-2.4 -4.9 -3.8": ["doctorial"], "-10.1 16.5 -0.5": ["shluchim"], "8.4 10.8 -7.5": ["fhe"], "22.2 12.3 13.9": ["soapsuds"], "16.0 26.3 6.9": ["djinns"], "4.0 12.9 11.4": ["moxidectin"], "-1.4 3.4 -4.7": ["ibml"], "11.6 -2.1 -1.4": ["schilling"], "6.0 6.3 12.7": ["theseason"], "19.9 13.4 13.8": ["aeronaut"], "-0.9 7.9 19.7": ["gue"], "5.5 26.2 7.9": ["embitterment"], "14.9 18.3 9.7": ["chavez"], "12.5 7.7 0.4": ["socios"], "6.0 10.0 9.6": ["analyzation"], "3.5 13.4 7.4": ["expiated"], "7.1 12.3 15.5": ["pineal"], "9.0 20.0 8.8": ["disjoined"], "-0.0 15.6 2.8": ["freeborn"], "2.0 13.4 6.0": ["precedented"], "1.9 3.1 4.3": ["decompressions"], "4.9 9.9 12.4": ["trocars"], "8.8 -1.9 5.7": ["rooflights"], "8.8 5.4 4.2": ["efter"], "8.7 17.0 13.0": ["infarcted"], "-3.8 6.1 10.5": ["nath"], "-1.2 18.3 8.6": ["sermonizes"], "3.5 16.0 4.8": ["garbles"], "10.3 23.4 11.5": ["powerslide"], "7.5 19.9 12.7": ["aphelion"], "11.6 8.3 12.3": ["dealio"], "15.2 11.7 15.1": ["schmoozy"], "-2.1 2.3 6.1": ["remainer"], "22.9 30.5 13.9": ["slavemaster"], "9.6 7.9 30.3": ["labneh"], "-5.0 13.0 3.6": ["sulphonylureas"], "22.6 9.6 13.6": ["thingamabobs"], "-0.0 6.5 8.4": ["saf"], "5.8 5.7 7.1": ["mesoporous"], "11.0 16.2 4.1": ["jailbroke"], "15.0 12.0 27.7": ["whitecoats"], "0.2 19.9 10.1": ["macheted"], "-11.1 21.1 11.0": ["dicipline"], "6.3 21.3 3.3": ["unrepentent"], "6.9 18.7 11.3": ["naivity"], "7.0 11.0 7.4": ["spectrometric"], "21.8 20.9 -5.2": ["blitzkreig"], "9.8 19.9 16.2": ["bluffers"], "8.9 11.4 1.9": ["possibilties"], "18.5 6.3 11.4": ["swiper"], "18.6 21.7 14.2": ["illimitable"], "1.9 9.4 7.3": ["ota"], "0.5 6.7 2.0": ["alumns"], "13.7 6.5 16.3": ["dogg"], "10.8 27.4 7.9": ["hindutva"], "4.8 7.5 12.4": ["multilayers"], "9.0 12.9 13.7": ["funking"], "-4.5 1.9 0.2": ["ichael"], "-0.1 2.3 9.0": ["silicas"], "13.4 0.9 21.4": ["semiprecious"], "6.7 -0.4 22.2": ["rara"], "16.7 8.9 20.2": ["tushes"], "8.6 14.1 10.4": ["fuckery"], "11.4 10.4 16.4": ["chiptunes"], "3.9 19.4 32.2": ["sowbugs"], "8.9 9.1 0.8": ["liftgates"], "2.1 21.9 3.2": ["denominationalism"], "6.9 -7.3 8.3": ["overbudgeted"], "-0.0 9.1 7.0": ["aerosolization"], "10.9 8.4 18.2": ["futebol"], "9.8 10.1 10.5": ["dadaist"], "11.1 23.7 9.0": ["goddamnit"], "0.9 21.7 2.6": ["underprotected"], "5.6 5.5 1.7": ["pitots"], "15.8 14.9 13.5": ["tred"], "-1.0 6.8 9.6": ["bedbound"], "6.2 22.8 14.0": ["gerrymanders"], "5.9 0.8 2.2": ["noncall"], "2.2 3.9 14.9": ["makita"], "0.5 13.3 1.8": ["convienent"], "-5.1 9.4 3.3": ["feedforward"], "12.6 29.8 12.0": ["sophism"], "17.6 16.4 29.7": ["bitey"], "-1.8 5.6 9.1": ["baithak"], "2.2 0.5 13.2": ["lookahead"], "5.0 15.6 3.7": ["whatev"], "7.1 -1.2 19.6": ["shiploader"], "5.1 6.0 12.1": ["isothiocyanate"], "7.2 14.5 18.3": ["creepin"], "21.5 10.0 18.1": ["archosaurs"], "3.9 28.3 22.4": ["upkick"], "5.9 9.3 25.2": ["unctuousness"], "9.1 12.7 6.1": ["brightnesses"], "10.8 12.1 15.4": ["nymphomaniacs"], "-0.3 15.9 14.1": ["stathmin"], "9.3 5.0 17.3": ["scrumpy"], "-5.9 11.0 7.3": ["donees"], "9.3 20.3 8.0": ["ultranationalism"], "7.4 6.4 7.6": ["multistrategy"], "-1.1 8.8 6.6": ["drving"], "2.7 5.4 14.5": ["barbershoppers"], "-3.7 2.4 -1.5": ["obiter"], "4.3 17.5 16.1": ["ofttimes"], "1.7 5.9 9.1": ["postnuptial"], "2.3 -3.1 11.5": ["develo"], "-0.9 -1.2 19.9": ["marijuna"], "6.5 4.3 7.1": ["bron"], "-5.9 5.0 8.1": ["thiazide"], "17.2 7.8 7.6": ["eque"], "20.5 12.3 14.3": ["torchlit"], "16.4 10.9 21.0": ["quivery"], "9.9 4.6 1.9": ["dressingrooms"], "-3.7 19.2 11.1": ["outstruck"], "11.0 6.1 5.8": ["colombia"], "5.8 5.1 8.9": ["alkane"], "3.8 2.5 6.8": ["electrospray"], "4.6 23.0 2.7": ["presidentialism"], "15.6 9.8 16.6": ["sunlounger"], "0.6 18.4 4.7": ["answerability"], "3.0 13.9 7.9": ["cymbalta"], "3.6 1.9 1.9": ["podcars"], "7.0 19.6 5.4": ["choas"], "-10.6 3.9 9.5": ["critera"], "-3.2 2.0 20.2": ["boatline"], "5.1 1.4 1.7": ["eyeonics"], "7.9 28.8 13.8": ["contemptibly"], "6.0 10.9 17.3": ["steele"], "0.1 0.3 2.8": ["microdialysis"], "-3.7 15.3 12.7": ["comaraderie"], "16.7 11.4 22.0": ["dumbells"], "13.1 9.0 21.2": ["effluvium"], "4.6 7.2 10.7": ["luvs"], "3.9 16.7 3.6": ["apologias"], "9.8 -1.4 6.7": ["blogdowntown"], "1.2 4.9 12.1": ["cartway"], "0.6 0.6 7.4": ["bankshot"], "12.9 19.4 11.9": ["paparazzis"], "3.4 -9.3 2.4": ["ioinet"], "11.9 8.6 21.3": ["glucomannan"], "17.8 7.4 10.8": ["nabob"], "7.9 7.1 3.3": ["ficials"], "12.4 5.1 29.5": ["affogato"], "6.5 7.4 22.5": ["midevening"], "20.7 10.8 8.1": ["rhapsodically"], "7.1 12.3 7.4": ["existe"], "25.2 16.6 14.1": ["uncomprehendingly"], "11.2 13.0 17.3": ["onanistic"], "5.7 -2.7 0.1": ["middler"], "6.6 3.1 3.9": ["closemouthed"], "10.9 0.7 -9.1": ["affilate"], "4.5 -0.6 14.3": ["chik"], "16.5 0.5 14.8": ["stemcell"], "3.0 5.2 6.1": ["aforestation"], "9.1 6.3 5.6": ["nx"], "-0.8 15.6 -1.9": ["imambargah"], "-3.0 19.3 1.4": ["faultfinding"], "1.3 1.4 9.7": ["anaylsis"], "5.8 10.4 14.1": ["mights"], "15.7 14.1 24.4": ["crocosmia"], "15.3 6.4 0.1": ["facebooks"], "7.7 1.6 15.6": ["hydromet"], "26.9 13.8 8.2": ["teutonic"], "-0.0 6.5 4.2": ["romanian"], "8.9 -0.4 4.9": ["glasstec"], "-3.8 -2.8 -6.3": ["ected"], "-7.3 11.4 5.6": ["ahmad"], "3.1 11.8 4.3": ["defragmenters"], "10.4 10.1 25.4": ["cockers"], "10.8 12.5 8.8": ["steeliest"], "10.9 20.9 7.1": ["eurocentric"], "2.3 35.8 5.8": ["unwounded"], "2.7 8.8 4.2": ["trigeminal"], "14.5 8.7 7.6": ["stablizing"], "16.1 5.8 14.4": ["tallboy"], "12.1 -2.8 2.9": ["lubricators"], "-0.4 -3.0 -2.0": ["ccm"], "8.7 11.3 5.5": ["aircore"], "4.0 14.9 13.5": ["dialectal"], "9.2 13.4 5.8": ["enraptures"], "15.1 25.8 6.0": ["bootprint"], "8.5 12.0 16.5": ["muda"], "10.7 9.1 5.2": ["ultraluxury"], "3.2 9.7 14.4": ["lester"], "11.5 6.0 32.1": ["haulout"], "12.4 2.3 -1.1": ["inbollywood"], "9.6 8.8 2.8": ["sucession"], "6.9 5.0 11.5": ["palki"], "-2.3 5.4 4.4": ["daughers"], "6.5 1.0 9.2": ["ostinatos"], "5.7 9.3 22.6": ["clayey"], "-5.4 1.1 10.2": ["cytologic"], "5.8 17.0 13.8": ["dearies"], "-2.2 3.2 13.2": ["perries"], "8.6 14.4 13.4": ["loquacity"], "20.5 7.9 13.0": ["prickled"], "8.7 8.3 6.0": ["freneticism"], "-0.5 5.8 7.2": ["matchable"], "0.5 24.2 6.7": ["perceiver"], "2.9 7.7 21.3": ["torrontes"], "17.6 8.5 6.7": ["collpase"], "9.3 4.6 1.3": ["streched"], "-2.5 12.5 4.1": ["innervated"], "1.4 13.9 18.5": ["livelyhood"], "7.6 -2.7 3.5": ["labelstock"], "-1.3 11.0 9.3": ["ependymomas"], "19.8 16.5 14.0": ["gimbals"], "2.7 18.1 5.6": ["intox"], "3.4 9.6 34.7": ["papads"], "6.2 5.0 0.6": ["fermionic"], "17.2 16.7 8.7": ["pluckily"], "15.8 18.2 31.3": ["flingers"], "4.3 13.2 14.4": ["centners"], "6.5 26.1 10.0": ["cohering"], "1.6 12.2 11.1": ["junctional"], "16.6 20.1 12.9": ["squealers"], "2.5 1.9 -3.0": ["explorationist"], "-2.9 16.3 7.8": ["electee"], "6.6 27.7 2.6": ["vigilence"], "-4.6 12.7 4.5": ["timeto"], "10.8 -3.6 3.6": ["uitgebracht"], "15.4 15.8 13.1": ["headded"], "4.8 4.1 0.4": ["retreaders"], "10.6 14.3 5.2": ["bigotted"], "8.2 22.6 3.3": ["exercize"], "17.1 7.2 12.3": ["lithesome"], "14.1 -8.2 10.6": ["papermill"], "9.7 10.3 16.5": ["phylogenetics"], "4.9 9.2 25.8": ["paddleboarders"], "3.7 4.0 11.6": ["umemployment"], "23.1 15.9 26.3": ["smooshing"], "2.2 20.9 1.4": ["securityman"], "7.9 16.7 8.0": ["helitankers"], "6.8 10.2 15.1": ["gats"], "8.8 10.1 17.5": ["chlorophylls"], "8.1 15.1 16.9": ["trypanosome"], "7.0 7.1 5.0": ["poisioning"], "5.5 4.0 -0.5": ["functionalised"], "8.1 6.5 8.4": ["berkeley"], "8.6 1.1 4.7": ["midsoles"], "9.1 5.8 37.9": ["tangs"], "14.3 16.6 18.2": ["southeaster"], "2.7 8.3 7.2": ["juvenility"], "0.6 13.9 7.7": ["progressivist"], "-0.7 4.7 9.5": ["activ"], "-0.4 5.2 13.9": ["topsoils"], "-2.2 13.7 -5.7": ["communcation"], "6.3 29.0 11.2": ["untermenschen"], "10.9 0.7 -5.1": ["theleading"], "8.9 6.0 3.1": ["pitbox"], "14.0 10.3 16.7": ["tumulus"], "8.8 10.8 13.8": ["tropomyosin"], "-3.4 13.3 5.8": ["denotifying"], "13.0 0.4 -11.2": ["digitalising"], "-1.0 3.0 8.2": ["heptane"], "10.0 12.2 11.1": ["fluidness"], "7.3 10.0 7.7": ["mighta"], "7.9 5.7 7.9": ["canefield"], "12.9 4.7 14.6": ["mair"], "10.8 11.6 21.3": ["skinful"], "5.1 6.5 23.3": ["glulam"], "13.4 13.9 18.7": ["unstack"], "1.1 17.0 6.3": ["caritas"], "-12.9 0.6 -1.7": ["laboratorians"], "23.0 9.3 23.1": ["dingle"], "12.4 6.5 7.1": ["jcoyle"], "15.8 4.3 17.3": ["dwr"], "8.9 2.8 3.7": ["sitework"], "3.5 10.2 7.1": ["cilengitide"], "16.6 28.5 1.5": ["facelessness"], "3.4 8.6 10.3": ["hyperplastic"], "24.5 21.3 19.1": ["noseless"], "0.2 4.5 6.2": ["perio"], "11.9 7.1 4.5": ["sahara"], "-1.2 1.0 5.5": ["francophonie"], "7.3 12.0 22.6": ["potables"], "6.6 9.0 18.7": ["pinoy"], "9.3 4.2 18.4": ["prepuce"], "2.6 10.7 11.5": ["tradables"], "2.2 2.5 15.6": ["grandaughters"], "3.5 5.9 7.5": ["fourgame"], "3.6 0.4 30.0": ["laing"], "21.3 15.9 5.0": ["decomissioned"], "9.9 21.6 9.7": ["incuriosity"], "2.1 6.2 0.3": ["geben"], "9.9 11.9 4.5": ["didactics"], "4.8 -0.6 10.3": ["mediabistro"], "-3.7 7.4 4.2": ["xxxxxxx"], "5.5 17.5 11.2": ["scatterometer"], "-2.9 5.7 4.6": ["admitt"], "-6.3 17.7 5.4": ["disfranchise"], "24.9 6.2 17.4": ["jacknifed"], "19.0 5.2 12.3": ["toliet"], "-2.9 16.0 10.4": ["ancestress"], "6.0 9.7 6.2": ["andthey"], "4.3 6.5 16.2": ["boatlengths"], "-1.7 9.9 1.3": ["yeshivah"], "-0.3 1.4 9.5": ["hydrolysed"], "7.5 -0.2 13.4": ["condominum"], "6.6 2.2 0.5": ["disaffiliating"], "22.9 11.7 9.8": ["bearhugged"], "-3.2 9.7 11.9": ["arrrived"], "5.7 8.0 21.4": ["fimbriae"], "0.9 24.8 11.3": ["herbicidal"], "-0.9 28.1 -0.8": ["debriefer"], "13.8 17.7 40.3": ["coontail"], "14.6 17.4 14.5": ["narcosis"], "13.4 25.6 22.0": ["aswang"], "-0.2 13.6 4.4": ["forewarnings"], "-2.4 4.4 8.1": ["thani"], "12.1 4.3 9.4": ["napster"], "7.5 16.1 12.2": ["bhais"], "6.2 15.8 1.8": ["locationing"], "3.2 14.1 10.5": ["sievert"], "4.7 18.0 5.8": ["equalitarian"], "15.3 19.9 11.3": ["outstretching"], "7.3 14.8 13.4": ["mcnabb"], "15.1 8.5 23.5": ["ferny"], "0.1 14.3 9.6": ["geohazards"], "-1.3 1.8 18.5": ["pongala"], "3.1 4.6 -1.9": ["critcised"], "11.4 8.5 18.2": ["furoshiki"], "-2.4 1.6 11.6": ["deok"], "8.1 15.2 -1.7": ["epitomes"], "1.1 14.2 13.4": ["fuzzer"], "10.0 1.5 13.3": ["hydrometallurgy"], "12.4 9.6 25.6": ["toasties"], "7.1 -1.3 12.5": ["zabaleen"], "5.2 0.1 6.3": ["topup"], "-0.5 8.5 3.5": ["metallogenic"], "4.6 13.1 14.0": ["cripes"], "14.0 21.3 10.4": ["jugulars"], "-1.7 5.8 15.7": ["sking"], "16.6 10.9 1.0": ["infrastrucure"], "13.3 10.0 10.7": ["appa"], "6.6 13.3 13.2": ["coarsen"], "11.5 9.4 21.3": ["simit"], "8.2 12.3 6.3": ["unuseable"], "8.3 -8.4 11.2": ["fundrasier"], "6.1 12.4 8.2": ["hup"], "-1.9 17.0 9.6": ["nstead"], "6.7 5.1 13.3": ["metalsmiths"], "9.5 17.2 12.8": ["meatgrinder"], "7.4 7.8 36.9": ["shortboards"], "9.2 2.6 20.0": ["benzopyrene"], "2.5 6.7 27.3": ["chawal"], "-0.6 16.5 5.1": ["waffly"], "0.8 21.0 7.7": ["linkmen"], "17.3 7.7 21.2": ["barfs"], "7.4 11.1 19.7": ["interspecific"], "14.7 6.0 8.1": ["absorbant"], "9.2 5.4 12.0": ["pornification"], "-1.3 9.5 4.3": ["guider"], "3.8 14.3 11.4": ["overnutrition"], "12.4 29.7 12.1": ["compassionless"], "18.1 11.5 9.9": ["yowled"], "21.2 8.4 16.3": ["bedsteads"], "9.0 6.3 -5.9": ["tobecome"], "5.8 -1.5 21.2": ["hereford"], "23.6 14.6 28.0": ["wiggler"], "10.4 7.6 17.9": ["eugene"], "-8.6 6.2 7.8": ["subprogram"], "16.6 12.3 37.1": ["nudibranchs"], "5.6 12.7 4.0": ["factbook"], "-9.1 6.8 3.4": ["mitigants"], "13.9 6.9 28.4": ["malanga"], "12.5 2.3 14.8": ["briskest"], "0.8 1.6 16.5": ["paano"], "0.5 11.4 1.8": ["reinducted"], "-7.2 2.7 5.5": ["faqs"], "8.3 13.0 10.5": ["bitchiest"], "8.0 3.0 13.6": ["taprooms"], "4.5 13.1 -1.7": ["novelisation"], "15.7 11.5 17.7": ["lolcat"], "17.7 13.8 16.0": ["tessellated"], "-4.3 16.5 -2.6": ["syed"], "2.2 5.6 11.8": ["anorectic"], "13.3 2.8 27.4": ["aquamarines"], "5.7 16.3 36.8": ["whitebaiters"], "13.3 6.0 6.7": ["cellulosics"], "16.6 11.6 18.7": ["goony"], "12.2 6.2 31.2": ["unsliced"], "4.9 6.7 4.9": ["convalesces"], "7.3 7.8 7.7": ["playng"], "9.2 6.1 13.5": ["passacaglia"], "15.1 16.9 20.4": ["sailers"], "4.0 2.7 19.0": ["parve"], "-1.6 3.9 10.4": ["sek"], "5.3 5.8 11.0": ["househusbands"], "14.4 -1.2 -3.0": ["swops"], "10.5 8.3 17.9": ["duro"], "6.7 11.3 17.5": ["defi"], "9.4 10.7 12.4": ["beleaguering"], "2.2 11.8 12.3": ["bactericide"], "3.8 5.7 2.4": ["dereservation"], "19.9 10.9 4.4": ["miniaturising"], "4.5 1.2 15.2": ["tota"], "3.4 11.4 11.7": ["premarin"], "13.0 10.0 18.0": ["pichkaris"], "0.6 0.6 2.1": ["lixivaptan"], "7.7 13.8 46.1": ["cutts"], "5.4 8.1 16.1": ["padrino"], "-6.9 7.7 5.2": ["dysuria"], "4.9 -0.5 31.4": ["entr"], "9.8 10.6 18.4": ["capsids"], "14.8 34.9 9.8": ["bayoneting"], "14.9 -2.0 11.7": ["eries"], "3.2 7.7 5.8": ["studiers"], "7.7 11.0 -2.9": ["potrayed"], "6.1 10.3 17.0": ["kindess"], "20.2 1.1 -0.9": ["ihotdesk"], "1.7 5.2 2.9": ["hommes"], "7.9 -1.8 29.2": ["dasheen"], "14.2 19.4 5.3": ["legations"], "16.0 11.0 26.0": ["ligustrum"], "11.0 3.3 12.0": ["microsuede"], "12.5 17.1 9.3": ["asininity"], "0.1 16.9 21.1": ["cantankerousness"], "10.7 6.4 8.2": ["bellyached"], "12.9 6.3 4.9": ["sidewards"], "10.7 -3.1 6.2": ["leatherwear"], "-1.6 3.0 7.3": ["orn"], "8.6 12.2 12.0": ["baldie"], "-0.6 23.5 6.3": ["materialistically"], "1.0 5.7 20.4": ["cana"], "18.2 15.8 6.5": ["magnetizes"], "4.5 11.9 14.5": ["endplates"], "6.3 31.0 6.5": ["kalashnikovs"], "4.3 2.5 14.4": ["holloware"], "3.9 7.5 7.0": ["panadol"], "-10.5 0.5 13.8": ["subfertility"], "8.8 11.7 15.3": ["tooooo"], "14.0 3.0 -4.4": ["digitises"], "7.9 24.4 8.1": ["accusative"], "8.8 3.3 2.3": ["animportant"], "12.3 13.4 1.7": ["kinkiest"], "-0.8 7.7 13.5": ["jeffrey"], "-0.5 -0.2 2.5": ["incisionless"], "9.2 10.1 13.9": ["dolmens"], "10.9 17.0 16.2": ["ratites"], "4.4 6.7 4.8": ["penetrometer"], "9.9 12.9 17.5": ["frottage"], "2.2 11.4 8.8": ["subcarrier"], "19.6 15.9 17.7": ["stompy"], "3.1 8.1 0.4": ["bodybugg"], "12.3 28.7 3.0": ["firer"], "8.6 12.4 -0.0": ["contemporizing"], "3.7 3.4 5.5": ["mandaps"], "8.5 18.6 10.9": ["unliked"], "5.6 25.8 5.2": ["carbomb"], "29.3 6.1 21.9": ["tubelike"], "5.7 9.9 5.6": ["adsorbing"], "7.1 1.4 -0.5": ["weniger"], "3.1 3.2 0.2": ["theosophy"], "6.7 9.7 25.5": ["seiche"], "1.1 11.7 -0.9": ["investigaton"], "21.0 9.4 33.1": ["tidepool"], "3.9 6.3 9.6": ["tokenized"], "12.5 4.4 37.0": ["calabaza"], "7.2 6.4 16.7": ["coastwise"], "16.6 16.0 8.9": ["fireproofed"], "10.2 3.0 32.8": ["bobotie"], "17.7 10.6 4.0": ["airhorns"], "5.4 5.0 1.5": ["mahants"], "11.2 14.5 15.4": ["beaurocracy"], "6.3 11.3 28.9": ["woodrats"], "9.4 12.8 15.2": ["boltcutters"], "3.2 2.9 2.2": ["gupta"], "-1.0 23.8 5.0": ["rightfulness"], "10.5 24.1 17.6": ["morans"], "-5.7 13.1 13.8": ["regressivity"], "-2.6 9.5 8.5": ["minorly"], "-0.7 8.5 9.4": ["anyhting"], "4.7 13.2 5.2": ["nonobvious"], "6.0 0.6 0.4": ["alliantgroup"], "4.7 1.5 7.0": ["norte"], "15.4 10.1 19.3": ["chics"], "-0.4 10.6 -3.1": ["reliablity"], "9.2 10.0 14.8": ["posterization"], "-2.8 18.1 4.4": ["sunna"], "1.7 -0.5 2.3": ["affadavits"], "4.5 11.5 14.2": ["acromion", "chitinase"], "7.6 -2.3 25.3": ["sao"], "1.3 -0.4 9.1": ["spraygrounds"], "10.4 7.2 23.3": ["trailerable"], "-1.1 -2.5 0.0": ["disqualifed"], "11.6 11.2 24.4": ["sunbath"], "5.4 17.0 11.4": ["unimplementable"], "-0.4 4.1 8.9": ["activin"], "13.5 13.2 4.6": ["unsavvy"], "11.5 6.3 -2.4": ["isnow"], "0.4 5.4 11.9": ["butterflier"], "3.6 7.2 9.4": ["quizzer"], "11.6 6.6 15.1": ["stratovolcano"], "6.5 -1.4 3.4": ["edie"], "11.8 7.3 8.7": ["jetons"], "9.0 1.8 3.2": ["oto"], "18.5 10.7 14.0": ["queerest"], "3.6 17.0 8.9": ["smalltalk"], "7.3 -3.5 5.1": ["meses"], "9.1 6.0 15.5": ["contining"], "13.8 14.7 21.3": ["goooood"], "13.1 2.8 0.7": ["ifa"], "15.9 14.2 10.9": ["phishes"], "4.7 5.9 6.8": ["uefa"], "1.0 -12.8 -1.7": ["studen"], "-0.4 -4.7 5.9": ["hsa"], "1.3 14.5 4.1": ["overinterpreted"], "-9.2 6.8 5.1": ["confounder"], "10.2 -5.5 20.8": ["quetzals"], "5.5 16.2 3.9": ["underreports"], "3.4 15.1 6.0": ["madhesi"], "15.7 8.4 8.6": ["heavylift"], "-3.4 5.8 18.0": ["desiltation"], "4.7 5.2 3.5": ["burglarised"], "1.9 10.5 -2.0": ["exerpt"], "1.1 -0.5 2.0": ["chanelled"], "13.1 3.1 2.2": ["qtags"], "5.9 13.1 14.6": ["vodou"], "8.5 5.1 14.1": ["interday"], "-0.5 13.6 11.6": ["karne"], "12.9 1.5 -1.6": ["heisting"], "-1.9 7.6 -0.2": ["workstyle"], "3.4 25.2 7.1": ["beligerent"], "5.7 17.5 7.3": ["causers"], "10.6 21.9 4.0": ["perniciousness"], "1.8 4.2 16.2": ["transcriptomic"], "7.8 -4.1 8.3": ["vihuela"], "19.8 17.4 18.6": ["flatliner"], "1.1 21.1 4.3": ["devided"], "19.8 15.0 5.0": ["geekily"], "7.3 3.9 7.7": ["cottah"], "14.8 14.9 11.6": ["philia"], "-0.4 15.6 10.6": ["unmarriageable"], "11.8 11.2 9.2": ["wuth"], "7.5 6.7 24.1": ["chinaman"], "7.7 5.9 -1.9": ["unwiring"], "2.6 9.2 7.8": ["metyrapone"], "-9.3 5.4 14.1": ["orthophosphate"], "8.3 10.7 7.8": ["germophobic"], "6.7 -3.2 11.9": ["boardslide"], "11.1 30.3 8.0": ["unhuman"], "13.3 0.8 41.5": ["dulse"], "5.3 1.4 13.1": ["makegoods"], "-3.5 16.3 16.1": ["povery"], "22.8 18.4 44.8": ["isopod"], "-8.3 5.4 4.7": ["codriver"], "15.2 -1.3 6.7": ["regio"], "2.3 5.2 13.8": ["carson"], "12.4 5.8 6.6": ["maemo"], "2.6 12.0 3.3": ["nilled"], "24.6 11.4 34.3": ["flippered"], "5.7 -2.3 5.0": ["methyltrienolone"], "-4.9 5.9 1.8": ["hypoperfusion"], "2.9 1.4 -4.5": ["nouncement"], "8.5 11.2 17.4": ["operatics"], "3.6 6.4 6.8": ["chelates"], "2.9 3.2 9.6": ["bidorbuy"], "23.4 17.4 17.9": ["thingamabob"], "10.4 1.4 7.3": ["shapeliness"], "2.9 2.4 23.3": ["meritage"], "7.9 4.4 26.7": ["argus"], "9.9 12.6 32.4": ["cheftestant"], "4.3 27.1 18.0": ["headedly"], "5.9 1.3 8.7": ["flanger"], "6.6 10.9 2.6": ["muscarinic"], "15.4 10.3 -0.2": ["rivetted"], "11.3 5.8 16.3": ["geolocators"], "2.2 7.9 3.4": ["motoric"], "8.0 8.2 -1.1": ["upgradations"], "28.2 8.2 13.9": ["coathangers"], "8.8 14.7 11.3": ["cks"], "5.7 22.0 4.8": ["outlands"], "1.2 14.0 -2.4": ["agasint"], "13.8 9.2 -1.2": ["sourcers"], "-7.9 9.5 13.8": ["laxed"], "0.8 4.7 4.9": ["incretins"], "-5.2 5.1 10.2": ["earhook"], "15.8 -4.2 12.9": ["mnth"], "-1.6 5.3 11.0": ["moz"], "3.4 8.0 4.7": ["nonacute"], "-4.1 8.1 4.3": ["teamworking"], "12.7 15.6 7.6": ["betweener"], "26.1 4.1 15.8": ["pawprint"], "2.9 6.6 7.8": ["carbamates"], "6.1 15.8 2.1": ["decieved"], "2.8 5.8 0.3": ["pemphigus"], "4.8 9.0 10.9": ["jaane"], "-2.0 2.5 -0.6": ["publc"], "9.9 -3.1 14.1": ["fiftyish"], "17.5 25.2 14.5": ["overinflate"], "-0.9 19.2 12.8": ["alwasy"], "6.9 4.5 5.5": ["coilover"], "3.8 6.7 -5.5": ["iglucose"], "18.1 19.9 8.1": ["timelord"], "8.5 6.3 19.5": ["anorthosite"], "17.5 9.5 11.2": ["lugubriously"], "3.9 8.4 15.0": ["mitti"], "-1.2 17.4 6.2": ["surplusage"], "4.4 8.1 6.9": ["onerously"], "5.2 7.7 8.4": ["maidans"], "6.5 -0.4 7.3": ["vertabrae"], "12.1 9.9 7.8": ["stucture"], "5.7 15.6 29.2": ["seacoasts"], "15.0 0.6 31.4": ["fideo"], "4.5 4.7 10.1": ["cilice"], "3.4 3.9 8.1": ["quiero"], "6.4 0.0 3.3": ["fufilled"], "9.6 2.5 4.8": ["limosine"], "11.4 11.7 8.4": ["primus"], "-3.1 12.9 12.4": ["mancini"], "2.9 8.1 10.0": ["metapneumovirus"], "-1.1 2.3 12.0": ["perkins"], "-7.7 19.7 5.3": ["mukhtars"], "-0.8 19.2 1.2": ["watan"], "4.3 0.9 14.9": ["commonage"], "-6.7 3.2 5.5": ["synodical"], "2.4 -3.1 12.3": ["pontiac"], "4.0 1.4 5.6": ["ancora"], "-11.6 18.6 2.2": ["hasan"], "12.9 10.6 13.3": ["greenwood"], "2.7 10.1 11.5": ["neurasthenia"], "7.8 -5.6 3.2": ["ceremoney"], "-1.6 -3.1 -1.7": ["dation"], "16.1 12.4 13.3": ["callisthenics"], "9.0 9.0 10.9": ["manos"], "14.6 14.3 9.7": ["stationmasters"], "19.7 10.1 29.2": ["lugger"], "-9.4 12.0 5.5": ["cirumstances"], "-3.5 10.7 12.1": ["granulocyte"], "1.2 2.5 15.0": ["reimbursables"], "4.1 6.4 13.3": ["sarili"], "14.4 11.4 25.9": ["brumby"], "5.5 10.1 4.9": ["unmastered"], "12.0 22.5 21.5": ["fowler"], "8.7 -2.9 13.8": ["jeh"], "3.0 7.6 13.5": ["racewalkers"], "1.7 -0.3 9.6": ["lithographers"], "9.5 19.8 14.1": ["degrating"], "11.3 15.8 10.4": ["caciques"], "1.4 -1.3 5.6": ["hdt"], "12.2 10.9 9.7": ["duchies"], "11.5 2.2 -0.9": ["shortcodes"], "-2.3 12.2 15.2": ["voteless"], "8.4 9.2 7.7": ["subpixels"], "22.6 12.0 11.2": ["micromachines"], "10.6 17.3 11.2": ["vikes"], "15.8 9.4 13.5": ["awwwww"], "-6.4 1.9 18.0": ["tino"], "1.1 4.9 12.1": ["tengo"], "-0.2 2.8 9.1": ["arsenide"], "8.5 5.0 14.3": ["putrescine"], "6.5 -1.0 7.0": ["anhydride"], "-3.7 2.5 7.0": ["musicial"], "0.2 16.2 -4.7": ["proclaimer"], "9.9 4.7 35.0": ["manok"], "2.9 -3.9 8.9": ["archtop"], "5.5 2.3 9.8": ["elles"], "0.6 9.4 9.4": ["aspirates"], "10.6 8.2 12.9": ["tailplane"], "9.2 10.3 5.1": ["worldchanging"], "7.2 8.2 9.4": ["pompeycarpet"], "9.3 13.4 11.0": ["hydrosphere"], "22.4 14.6 27.6": ["dewdrop"], "2.3 -0.7 9.6": ["nego"], "18.4 17.0 13.0": ["torchlights"], "-1.4 4.2 11.8": ["fasciotomy"], "11.7 11.0 28.3": ["snowberry"], "-0.8 13.2 9.9": ["inarticulateness"], "7.4 -4.0 13.2": ["tge"], "0.9 -6.2 -2.2": ["befound"], "0.2 -0.3 22.6": ["suji"], "4.6 10.6 16.3": ["pegmatitic"], "14.3 4.2 19.2": ["smokeable"], "-1.2 4.3 4.2": ["interposers"], "7.2 6.2 4.9": ["threatre"], "8.7 39.2 11.1": ["claymores"], "1.7 5.2 31.5": ["rahui"], "1.0 -5.1 9.4": ["tels"], "20.5 12.2 14.8": ["slimier"], "6.5 3.6 5.1": ["amphiphilic"], "9.2 0.8 22.1": ["frothiest"], "5.7 1.2 5.8": ["komen"], "3.0 5.6 10.0": ["dwg"], "9.6 18.4 14.2": ["lowness"], "11.1 10.4 8.3": ["ballscrew"], "12.1 6.5 4.2": ["creepfest"], "8.7 -1.2 16.0": ["cious"], "-2.7 6.6 16.5": ["exudative"], "2.8 3.2 -1.4": ["coverting"], "7.3 15.4 15.4": ["consumeristic"], "-0.2 7.5 5.4": ["inquries"], "11.8 5.3 6.9": ["fianci"], "22.7 16.8 17.0": ["dratted"], "12.4 9.9 28.4": ["arbutus"], "-2.6 4.8 9.7": ["dq"], "3.5 15.8 20.6": ["shipmaster"], "3.1 16.2 6.2": ["poz"], "2.3 12.2 -7.4": ["admininstration"], "3.3 10.1 11.9": ["subpixel"], "8.1 22.8 12.4": ["nanobees"], "5.5 13.7 30.1": ["emerger"], "7.9 -0.7 6.8": ["dexfenfluramine"], "-2.8 15.7 -0.5": ["forgetable"], "3.9 -2.5 6.9": ["respectivley"], "-8.3 10.6 6.9": ["nonemergencies"], "6.8 5.4 13.3": ["quess"], "6.8 17.1 11.9": ["weath"], "7.9 -6.8 2.2": ["cie"], "1.4 8.2 0.9": ["augmenter"], "6.1 6.6 18.9": ["heartlanders"], "7.9 16.7 10.4": ["whitefellas"], "-4.7 8.2 7.1": ["unsensational"], "12.7 10.1 23.2": ["habitant"], "7.9 13.5 2.4": ["teleprinter"], "7.6 10.1 25.9": ["milkvetch"], "2.3 10.6 8.2": ["isotype"], "6.4 2.4 14.0": ["disposers"], "11.2 5.6 28.8": ["gata"], "19.3 11.1 15.4": ["bedazzles"], "3.0 9.7 9.8": ["gaucheness"], "9.6 6.2 17.2": ["woodchopper"], "10.8 18.8 12.0": ["parvenus"], "1.3 9.4 11.4": ["nul"], "0.2 8.6 -0.5": ["invigilating"], "2.5 11.5 13.8": ["jurisidiction"], "8.6 15.4 25.1": ["dreds"], "9.6 4.0 4.4": ["egoli"], "8.2 18.9 4.1": ["purgation"], "4.8 30.2 5.4": ["baghdad"], "3.4 9.8 2.6": ["longerterm"], "18.5 7.1 28.8": ["aquas"], "8.1 6.0 5.5": ["robing"], "1.5 -10.4 -4.1": ["directorof"], "2.7 7.9 6.8": ["doubleplays"], "4.9 8.8 10.3": ["discontinuously"], "1.6 4.2 10.4": ["acequias"], "20.9 25.2 24.7": ["forepaws"], "12.6 25.2 7.4": ["dazing"], "4.1 -2.1 8.6": ["morrison"], "7.9 16.7 4.0": ["probelm"], "15.8 22.3 21.7": ["harpooners"], "19.1 18.3 9.8": ["biogenetic"], "16.7 4.2 17.3": ["humpty"], "-3.1 9.0 8.8": ["stf"], "-5.7 -2.6 3.6": ["photostability"], "0.9 -4.7 12.0": ["jogathon"], "6.1 15.0 14.9": ["whent"], "6.7 20.8 8.3": ["gazillionth"], "15.7 27.0 10.4": ["subspace"], "-2.4 8.4 3.9": ["unbeated"], "-2.7 7.8 21.0": ["planchets"], "14.9 27.6 7.8": ["sensationalists"], "21.1 2.6 24.4": ["bootiful"], "20.4 7.3 20.4": ["slater"], "-10.2 8.6 0.9": ["jured"], "5.3 8.3 17.3": ["bassman"], "14.0 15.1 7.9": ["defocused"], "15.1 7.0 16.2": ["horsedrawn"], "1.1 7.6 11.7": ["thrombospondin"], "7.7 13.7 31.3": ["midlake"], "2.3 11.3 15.4": ["eardrops"], "15.0 6.2 21.6": ["liatris"], "9.7 15.4 6.7": ["rebirthed"], "14.4 11.4 17.9": ["stereographic"], "-0.3 2.6 3.5": ["ecodesign"], "-3.2 11.3 8.9": ["thereare"], "11.0 16.2 19.1": ["mancs"], "8.0 10.5 6.0": ["proteinase"], "-6.7 13.9 5.3": ["thecase"], "0.5 9.6 -11.4": ["statemen"], "-3.1 -1.9 9.5": ["biopsychology"], "7.3 5.3 19.3": ["firewalking"], "2.2 17.1 10.3": ["engrossingly"], "5.6 2.4 4.9": ["lignocellulosic"], "9.1 5.7 17.4": ["interannual"], "2.5 11.3 6.8": ["megabases"], "4.5 9.1 4.8": ["multiviewers"], "4.7 8.0 8.3": ["chloritized"], "2.0 10.2 17.0": ["getable"], "-3.2 9.7 2.2": ["ashtanga"], "10.7 18.4 12.6": ["bumpersticker"], "14.9 11.4 16.9": ["geeze"], "4.1 13.6 5.5": ["backliners"], "10.7 14.4 23.5": ["understorey"], "5.2 11.0 5.7": ["pizzini"], "2.3 11.4 7.1": ["suspenser"], "0.7 1.1 9.5": ["eyelift"], "3.1 19.7 10.8": ["honorables"], "4.5 -5.1 -1.7": ["committeee"], "27.8 10.3 16.5": ["hulky"], "2.6 5.7 6.9": ["pathname"], "14.3 6.2 20.9": ["weimaraner"], "4.1 13.6 7.3": ["rhythym"], "12.1 14.5 11.8": ["vibroseis"], "8.2 9.4 0.1": ["developping"], "13.5 7.0 15.1": ["stramash"], "13.1 11.5 7.3": ["quaters"], "1.1 23.6 2.5": ["overdramatizing"], "0.6 15.2 -0.5": ["univocal"], "15.4 13.0 11.8": ["hewould"], "2.8 15.2 13.1": ["overenthusiasm"], "7.1 7.4 -5.1": ["petrbuben"], "-8.4 2.7 13.1": ["flagrants"], "-1.8 6.0 7.6": ["arisings"], "8.6 16.4 13.8": ["lmfao"], "7.1 13.0 5.5": ["doorstepping"], "13.2 2.2 39.8": ["winkles"], "14.7 21.3 19.6": ["sideslam"], "1.7 8.1 12.2": ["eumelanin"], "2.7 8.6 19.5": ["xiang"], "12.2 1.7 3.0": ["rerate"], "8.2 9.5 7.5": ["palled"], "-1.9 8.3 2.3": ["conspicuity"], "0.9 -2.1 7.9": ["lasy"], "11.4 11.8 4.2": ["conjoins"], "9.4 3.8 16.9": ["bacopa"], "-4.0 16.6 -2.1": ["complaintant"], "2.1 15.3 6.4": ["kilopascals"], "16.3 4.2 12.4": ["lapdancers"], "0.9 7.0 11.1": ["kemm"], "15.1 -4.2 8.9": ["unbid"], "12.0 14.3 -1.5": ["evangelizer"], "-4.2 6.5 -1.2": ["askes"], "1.9 9.8 21.3": ["kena"], "2.0 -1.7 8.6": ["bedwear"], "4.9 2.8 4.2": ["hvac"], "23.9 14.6 20.0": ["dalek"], "6.9 -6.4 9.1": ["predesign"], "11.8 19.8 7.9": ["beggaring"], "0.7 -1.2 5.4": ["fiche"], "9.9 1.6 0.2": ["vulcanology"], "1.9 5.4 9.2": ["withdrawable"], "14.7 2.1 -2.8": ["corporatising"], "4.6 5.8 5.8": ["imm"], "-1.9 -0.2 6.8": ["cathaoirleach"], "8.0 14.3 6.5": ["renaissances"], "0.6 7.8 2.4": ["mecamylamine"], "-0.7 1.3 3.1": ["solventless"], "4.3 2.4 6.9": ["gener"], "-1.6 18.3 14.1": ["reguardless"], "3.2 8.5 7.8": ["nicholas"], "7.7 12.1 34.1": ["frangipane"], "5.0 -0.7 11.7": ["nfs"], "1.5 -5.7 2.2": ["annualization"], "0.1 14.3 5.9": ["exaggerator"], "2.5 12.2 -1.8": ["beome"], "-3.2 1.5 7.7": ["acidized"], "-5.7 6.3 2.0": ["huband"], "1.6 1.1 9.3": ["stockmanship"], "2.8 -3.0 7.4": ["columbariums"], "4.8 12.9 5.8": ["refactored"], "14.5 17.1 8.9": ["neigbors"], "10.2 9.6 30.1": ["teppan"], "8.9 1.6 2.5": ["datebooks"], "18.0 5.0 5.9": ["manfacturing"], "17.2 9.8 20.0": ["biomineralization"], "-4.6 2.1 7.2": ["assigner"], "11.8 18.4 24.3": ["cloaca"], "7.3 27.7 2.4": ["thermobaric"], "14.9 10.0 3.6": ["worths"], "7.1 2.8 9.1": ["hillclimbs"], "9.3 4.6 14.1": ["protools"], "7.4 -0.6 18.5": ["rovings"], "7.1 4.8 7.7": ["weathertight"], "-0.0 13.8 -1.5": ["noninfringing"], "-4.4 4.4 5.9": ["gliclazide"], "3.3 -1.4 -4.0": ["aspecial"], "7.9 14.0 23.0": ["culms"], "8.2 9.6 13.8": ["incubations"], "3.6 12.4 35.0": ["pallids"], "-2.2 4.0 13.7": ["pinweight"], "1.6 19.1 8.3": ["jakester"], "2.5 6.3 15.4": ["kongsi"], "13.7 -1.6 13.7": ["completo"], "6.7 21.5 8.4": ["unfalsifiable"], "-0.7 12.2 15.8": ["dermatophytes"], "10.3 -2.8 18.8": ["nosegays"], "-6.1 17.7 0.7": ["beteen"], "14.3 16.5 25.1": ["oviducts"], "1.8 3.8 14.3": ["awr"], "9.6 13.4 16.0": ["grizzling"], "6.1 13.4 7.7": ["weeped"], "0.9 3.0 15.0": ["distaffer"], "7.8 11.4 29.8": ["columnaris"], "17.7 20.1 5.9": ["transmogrifying"], "2.7 4.1 9.0": ["ligated"], "8.2 6.2 32.4": ["duc"], "0.4 26.0 6.6": ["terorrism"], "8.5 14.6 6.4": ["womanisers"], "0.6 8.8 15.3": ["placepot"], "-3.9 9.1 2.0": ["resynchronization"], "13.5 9.1 20.1": ["chrism"], "-1.8 1.1 8.3": ["hypoplastic"], "-3.2 4.4 8.9": ["poloxamer"], "6.3 4.3 4.0": ["usherettes"], "5.3 4.0 23.5": ["freezin"], "-5.1 8.2 5.5": ["seatbelted"], "5.0 15.0 4.7": ["unsettlement"], "7.9 18.0 16.0": ["nerdery"], "2.7 11.2 13.7": ["ecotypes"], "14.1 10.8 10.4": ["modchips"], "7.4 4.2 3.3": ["valu"], "8.4 8.3 11.4": ["kiranas"], "20.2 6.6 18.1": ["tackily"], "9.0 23.3 14.7": ["molotov"], "-0.1 10.2 -2.8": ["taggant"], "8.8 17.2 5.5": ["cyberfraud"], "20.7 25.5 38.7": ["stonefish"], "11.6 4.5 10.1": ["zembly"], "-3.1 5.9 11.1": ["downwinder"], "6.5 19.5 3.2": ["dustin"], "-3.5 3.2 0.7": ["threetime"], "6.9 2.6 12.0": ["joi"], "6.6 22.1 0.8": ["hardbitten"], "-1.7 9.2 6.3": ["preclinically"], "2.3 12.2 7.4": ["kabbalist"], "16.1 10.6 8.9": ["agit"], "2.8 5.5 5.7": ["tizanidine"], "4.3 5.5 22.4": ["purpurea"], "14.8 9.5 19.8": ["noah"], "8.5 14.1 19.6": ["shinguard"], "-11.9 1.6 5.4": ["trihalomethane"], "-0.0 8.6 8.7": ["ligamentous"], "4.0 -1.7 0.8": ["overclaimed"], "-2.5 7.6 15.2": ["ganitong"], "6.3 15.6 8.7": ["euphony"], "4.0 5.5 3.9": ["lenser"], "2.3 10.5 5.3": ["yada"], "19.5 8.5 2.8": ["epaper"], "-1.7 3.9 4.3": ["clobazam"], "6.8 7.9 12.6": ["sacerdotal"], "9.9 17.5 11.9": ["outleap"], "-2.6 3.6 8.1": ["subcommission"], "25.5 7.6 -4.2": ["superbrands"], "23.1 15.1 13.7": ["wacking"], "10.8 12.1 17.4": ["whities"], "2.3 13.1 25.0": ["pumpboat"], "-0.8 4.5 6.5": ["degassed"], "-4.7 -1.9 2.3": ["officiation"], "19.6 6.5 40.4": ["claypot"], "-1.3 1.7 21.0": ["jwa"], "-3.6 -0.7 -5.8": ["progr"], "9.8 38.2 7.4": ["summoner"], "4.8 -2.6 2.4": ["concer"], "7.0 2.6 19.0": ["wharenui"], "-1.4 5.7 3.2": ["lomitapide"], "9.6 8.9 9.9": ["sternums"], "5.3 5.6 24.6": ["meadery"], "7.6 7.8 11.8": ["photocatalysis"], "16.7 6.6 19.4": ["tomo"], "3.6 11.3 41.3": ["panfishing"], "-1.3 11.3 -1.9": ["knwo"], "18.0 14.3 51.2": ["pogy"], "18.7 -2.5 11.7": ["megamillions"], "2.2 12.2 4.5": ["explant"], "-2.6 -1.7 12.9": ["lds"], "14.6 5.0 17.2": ["baile"], "14.4 10.2 13.6": ["reattaches"], "-10.3 -1.6 -12.5": ["intervew"], "7.3 3.8 12.9": ["docos"], "17.7 22.5 39.5": ["skua"], "7.4 -4.8 -0.9": ["todiscuss"], "4.8 7.3 2.7": ["forbad"], "1.9 6.7 7.7": ["dereserved"], "1.1 12.9 2.5": ["straightfoward"], "-1.0 14.1 8.9": ["stammerer"], "11.3 15.2 12.7": ["tearstained"], "-2.2 11.4 13.4": ["fibroadenomas"], "7.7 2.6 19.3": ["mycologists"], "22.8 10.6 -4.1": ["subsidaries"], "-4.4 -12.4 -5.4": ["drector"], "9.1 9.7 3.5": ["decomissioning"], "15.0 16.1 17.5": ["deregulators"], "-6.5 2.7 9.2": ["rance"], "-0.5 -0.7 3.4": ["housecalls"], "7.2 11.3 13.3": ["dora"], "18.0 11.9 23.3": ["moonstones"], "8.5 3.2 -4.5": ["rockband"], "4.7 5.4 1.7": ["snarkier"], "1.4 -1.5 3.3": ["densitometry"], "23.9 -0.4 30.3": ["iceless"], "5.2 5.6 1.2": ["challening"], "23.2 15.3 7.4": ["mangler"], "1.8 15.9 10.9": ["imamate"], "-1.3 15.3 3.5": ["muhammad"], "20.2 7.0 25.2": ["oinks"], "-3.0 1.5 -0.6": ["tarenflurbil"], "-1.8 16.1 1.7": ["didactically"], "15.8 22.2 8.4": ["stumbler"], "3.5 5.4 14.3": ["groundwaters"], "-2.5 2.9 5.5": ["nontendered"], "7.7 1.3 15.4": ["thimerosol"], "17.3 9.5 29.2": ["onigiri"], "11.5 8.6 23.2": ["habanera"], "7.0 11.8 15.9": ["frogsplash"], "7.6 14.9 5.0": ["bork"], "7.9 3.6 27.2": ["armagnac"], "16.6 10.2 13.1": ["aorund"], "5.2 8.4 8.3": ["nepalnews"], "3.0 7.5 7.2": ["warewashing"], "10.3 4.3 19.1": ["superchef"], "3.7 17.9 5.9": ["polititians"], "6.5 27.2 9.4": ["fighing"], "14.6 8.0 14.5": ["pulverizer"], "3.1 22.5 7.1": ["lanka"], "7.1 7.5 10.2": ["betoken"], "8.3 14.6 18.1": ["crystalizes"], "-7.3 -0.1 -2.7": ["confered"], "11.4 18.8 11.5": ["geoeconomic"], "11.8 10.0 16.1": ["touristed"], "4.3 -2.4 17.7": ["boca"], "7.4 12.5 10.5": ["hiragana"], "12.5 8.0 11.0": ["sassily"], "6.6 17.5 3.7": ["outraces"], "2.2 3.6 17.5": ["paniculata"], "7.6 0.7 3.7": ["glazings"], "7.9 8.4 14.8": ["jum"], "1.7 2.7 16.1": ["kyong"], "-1.3 18.8 -0.3": ["systematical"], "2.3 8.0 7.1": ["cityside"], "16.5 9.3 10.1": ["outpriced"], "5.6 6.4 9.0": ["hotpress"], "0.1 14.7 6.4": ["prisioners"], "19.6 13.7 16.9": ["tranquilising"], "9.0 8.1 17.7": ["aphrodisiacal"], "1.0 0.2 0.8": ["reindustrialization"], "18.2 13.6 19.6": ["justs"], "-1.2 13.2 6.6": ["acceptible"], "15.6 17.6 15.8": ["owies"], "-6.8 17.2 6.1": ["ototoxicity"], "5.2 -3.5 -0.5": ["xpress"], "-6.0 2.4 14.6": ["kaempferol"], "16.6 7.9 19.5": ["ragin"], "11.5 6.1 17.3": ["agarose"], "13.4 6.8 27.3": ["caramelly"], "2.3 6.1 2.5": ["theresults"], "14.5 15.8 6.7": ["timewaster"], "-0.0 37.6 11.9": ["incommunicable"], "6.1 5.5 18.2": ["thandai"], "20.8 8.3 19.7": ["cockies"], "9.2 26.5 6.2": ["unthankful"], "2.4 9.7 7.4": ["quailty"], "2.4 13.7 -2.0": ["dmedia"], "11.9 13.4 18.8": ["rajah"], "8.9 18.9 15.5": ["congeries"], "12.5 6.4 5.4": ["robosigning"], "0.0 19.8 11.2": ["koans"], "5.4 14.2 5.0": ["evangelised"], "4.1 5.9 11.7": ["puggles"], "2.9 11.8 8.1": ["unshockable"], "2.7 6.8 22.8": ["flowages"], "-0.9 5.7 -0.2": ["tter"], "10.5 11.6 14.6": ["hoiked"], "6.4 10.1 6.6": ["digusting"], "2.2 7.5 10.2": ["niveau"], "9.5 21.3 7.7": ["unfun"], "7.9 20.9 18.6": ["gogoplata"], "10.2 20.0 10.6": ["prophesizing"], "8.9 2.5 1.0": ["originaly"], "5.0 4.0 21.8": ["famiglia"], "0.1 4.9 6.5": ["deferiprone"], "4.1 6.1 31.1": ["fattoush"], "7.6 15.4 16.8": ["balck"], "24.7 5.4 33.6": ["catfood"], "4.4 4.3 7.3": ["arboreta"], "0.3 0.6 2.0": ["benzoylecgonine"], "-1.3 12.0 6.9": ["tortfeasors"], "13.9 10.5 7.8": ["murram"], "3.9 0.6 -4.2": ["idated"], "11.9 16.9 14.2": ["clintons"], "-1.3 21.8 13.7": ["behavour"], "2.2 9.8 11.2": ["unreacted"], "22.7 33.2 18.6": ["dreadnoughts"], "-4.7 9.3 6.3": ["ecchymosis"], "9.2 0.0 7.1": ["pacs"], "8.9 4.2 14.0": ["quat"], "-4.2 7.6 -8.0": ["messsage"], "8.8 5.6 37.5": ["redcurrants"], "-4.5 -3.4 5.5": ["ues"], "14.9 3.1 12.1": ["supernanny"], "2.4 16.3 6.7": ["mappable"], "19.0 8.3 8.3": ["subindustry"], "9.8 12.9 19.5": ["sundrenched"], "15.2 16.6 11.9": ["vaporises"], "0.7 6.0 -0.0": ["neurophysiologists"], "11.5 10.2 4.8": ["filterless"], "12.9 19.8 16.1": ["diabesity"], "17.0 -3.4 14.7": ["oneoff"], "0.8 13.3 7.3": ["ourability"], "5.6 3.8 19.1": ["paco"], "12.3 -0.0 11.1": ["descant"], "12.0 11.8 36.6": ["eggers"], "8.0 27.1 11.7": ["immortally"], "17.4 0.5 26.8": ["wickerwork"], "9.9 7.2 15.3": ["blownout"], "12.2 4.3 19.4": ["toastier"], "14.5 6.9 0.5": ["multibank"], "2.0 28.1 11.6": ["compleat"], "15.9 -2.8 13.2": ["tiendas"], "5.6 2.5 23.9": ["refrigerates"], "2.5 5.5 13.0": ["tanda"], "15.0 2.1 6.3": ["flaik"], "6.0 9.4 19.7": ["discing"], "-1.7 1.4 2.0": ["nanopowders"], "7.0 4.5 1.7": ["evangelically"], "-1.8 8.3 10.3": ["loveteam"], "11.3 7.3 16.9": ["basura"], "2.5 13.4 7.8": ["runline"], "-3.6 14.5 6.3": ["choosed"], "12.4 0.2 28.2": ["nettings"], "12.0 6.8 18.2": ["nanas"], "4.4 1.3 26.6": ["gracilis"], "10.2 21.2 6.5": ["beaconing"], "5.6 18.4 16.7": ["multishot"], "-4.6 5.3 11.5": ["blendstock"], "10.9 10.1 23.6": ["wun"], "-0.1 14.5 13.1": ["famliy"], "6.7 -6.5 -2.5": ["ideastream"], "14.1 19.2 12.1": ["slashtag"], "13.6 3.8 8.8": ["carbamide"], "13.5 10.5 21.7": ["henbane"], "7.8 7.4 13.0": ["rellies"], "10.4 11.9 2.5": ["hearsays"], "6.0 6.0 15.9": ["hermanos"], "2.5 21.0 7.0": ["marianne"], "-0.4 4.2 3.3": ["jain"], "6.2 20.4 13.0": ["firetraps"], "11.5 22.7 7.3": ["antiauthoritarian"], "6.7 5.1 -11.9": ["communcations"], "-4.0 6.4 4.6": ["pracharaks"], "19.7 4.7 18.0": ["silvering"], "9.1 6.3 12.1": ["bladers"], "6.3 12.3 8.5": ["nondivision"], "15.4 -1.3 17.9": ["feria"], "-2.5 22.6 4.0": ["decolonised"], "5.5 18.4 5.0": ["killling"], "2.3 17.3 6.0": ["counterfactuals"], "15.2 7.0 26.3": ["adzes"], "1.0 1.1 12.1": ["tammy"], "6.3 24.7 13.6": ["peolpe"], "5.9 5.0 12.5": ["unas"], "5.8 5.5 7.5": ["salvinorin"], "1.5 -6.3 4.2": ["golfwear"], "2.2 4.4 10.5": ["houseowners"], "10.3 15.4 4.2": ["unskippable", "crossway"], "8.9 0.5 10.0": ["kwong"], "11.8 3.6 37.4": ["kangkong"], "-0.7 -3.4 -4.3": ["affilated"], "10.0 0.9 35.5": ["salame"], "-11.6 -2.5 7.8": ["meher"], "5.2 2.3 4.5": ["bph"], "0.4 5.0 1.7": ["encourge"], "6.3 -2.1 -2.4": ["presitigious"], "-4.8 14.2 14.2": ["katta"], "17.1 6.5 6.7": ["spaceline"], "-1.5 9.2 15.8": ["lenge"], "3.7 5.7 6.5": ["dilaudid"], "12.8 22.7 2.5": ["dubya"], "7.7 18.2 11.9": ["yuo"], "10.9 7.6 3.7": ["pela"], "1.9 0.0 -0.3": ["medica"], "-0.9 19.2 3.9": ["blahblahblah"], "1.6 3.9 6.0": ["vasodilatory"], "14.1 9.9 3.1": ["congests"], "16.7 6.2 26.4": ["psychedelica"], "17.3 7.2 14.7": ["vestors"], "6.6 14.3 13.3": ["fuk"], "13.5 10.3 17.8": ["hooley"], "9.2 2.5 5.8": ["granulators"], "13.7 -1.2 31.4": ["cabrito"], "24.5 11.9 10.5": ["trigging"], "-0.9 1.9 4.9": ["macrosomia"], "8.7 12.0 17.9": ["slobbish"], "10.2 16.4 12.8": ["doggoned"], "10.8 13.7 -1.1": ["radiometry"], "6.1 -3.3 13.6": ["blanca"], "-0.2 -2.2 5.4": ["samitis"], "2.0 6.3 1.5": ["nanoliters"], "15.1 8.5 30.1": ["beany"], "17.5 2.2 31.7": ["thickish"], "2.3 2.9 9.3": ["iyung"], "14.7 7.3 -2.7": ["mobilkom"], "-0.2 16.4 2.1": ["intercessory"], "-1.2 -0.8 8.4": ["overprints"], "-2.9 13.6 -2.2": ["watchlisting"], "6.7 14.7 8.9": ["gamestop"], "4.5 16.4 7.3": ["safties"], "12.5 20.9 33.4": ["wapiti"], "3.0 10.5 16.9": ["fretfulness"], "19.9 3.0 16.2": ["tufty"], "5.4 25.1 3.7": ["halftrack"], "-1.0 0.9 7.2": ["estacode"], "17.0 9.4 7.8": ["cnc"], "5.5 2.6 5.7": ["hawn"], "8.0 15.5 -1.3": ["decontaminant"], "3.0 6.9 4.6": ["austria"], "14.5 2.8 17.1": ["blowzy"], "13.1 7.8 7.5": ["coreless"], "1.6 5.9 10.3": ["diez"], "-6.7 19.0 3.0": ["noncoercive"], "-2.2 7.3 10.6": ["aniya"], "16.0 -5.9 13.1": ["bathware"], "-1.3 8.9 4.8": ["utilizable"], "0.8 4.1 9.5": ["mesenteric"], "10.6 -3.4 19.9": ["ished"], "3.7 11.6 2.8": ["spotkicks"], "-7.4 21.0 8.1": ["blameworthiness"], "1.4 11.9 5.3": ["pithiest"], "-0.0 7.0 13.6": ["sois"], "14.9 5.1 23.6": ["gobbed"], "5.7 5.7 -7.0": ["mbrace"], "-10.9 0.6 3.5": ["minyans"], "1.2 22.0 10.4": ["territorials"], "10.5 4.3 13.5": ["sourthern"], "8.3 3.6 5.0": ["stageshow"], "8.3 0.4 -2.3": ["reprivatization"], "2.0 5.5 -1.0": ["endocardial"], "5.7 16.3 20.5": ["southwesterlies"], "6.6 0.6 10.6": ["soaper"], "-5.4 11.1 3.6": ["diksha"], "6.1 15.6 9.2": ["fandoms"], "-3.4 7.3 8.8": ["reamining"], "20.3 7.5 3.5": ["financialized"], "-7.6 3.7 15.8": ["glucosinolate"], "5.0 5.8 10.5": ["samithi"], "5.4 7.1 6.9": ["interuption"], "8.3 16.0 9.8": ["cellie"], "1.4 14.9 3.6": ["underseeded"], "7.0 17.0 10.1": ["overtrick"], "20.7 12.1 5.6": ["sunglassed"], "3.0 21.6 -0.9": ["inferentially"], "3.7 17.0 18.6": ["sinkerballers"], "-15.6 8.9 -5.8": ["watchlisted"], "8.1 2.0 7.8": ["overinflating"], "7.2 -0.1 12.9": ["otorhinolaryngology"], "4.7 7.9 13.3": ["bunding"], "1.0 7.9 14.1": ["janam"], "0.2 16.0 5.8": ["cuase"], "15.4 7.5 12.7": ["recrossed"], "0.5 34.4 4.0": ["mullas"], "10.6 11.6 8.9": ["addy"], "3.7 7.0 12.6": ["jambands"], "7.5 16.5 7.1": ["precolonial"], "-7.1 10.3 8.0": ["rosh"], "4.0 12.6 13.0": ["mulattos"], "6.7 4.9 4.4": ["weened"], "0.1 3.8 14.7": ["worldlier"], "2.3 10.8 6.7": ["incents"], "2.1 7.9 38.4": ["shellfisherman"], "0.9 4.4 0.6": ["addding"], "-3.8 11.3 4.3": ["multicentric"], "11.2 6.8 17.8": ["zyban"], "2.4 4.1 1.1": ["sulfated"], "-0.9 17.0 21.8": ["estrous"], "-5.6 10.6 7.4": ["phosphorylate"], "-2.4 -0.9 11.0": ["madi"], "8.6 -1.3 14.8": ["bookazine"], "15.2 16.2 24.4": ["blowpipes"], "1.3 -0.7 12.6": ["athenaeum"], "3.4 -1.3 19.2": ["kag"], "-2.4 1.9 16.2": ["dara"], "8.6 5.7 14.9": ["overmolding"], "13.8 -6.6 9.8": ["needlecrafts"], "12.1 7.6 9.1": ["unsnap"], "15.2 10.0 12.2": ["metropoles"], "3.2 13.6 -3.4": ["percept"], "5.1 10.8 12.7": ["troppo"], "0.7 15.6 11.3": ["feverishness"], "19.1 19.0 4.8": ["blabbers"], "1.6 14.5 9.5": ["qbs"], "15.1 13.6 26.2": ["pupal"], "8.6 7.4 3.5": ["centerd"], "2.5 13.4 3.8": ["heisman"], "16.1 1.0 7.8": ["utlity"], "-2.3 -0.7 24.4": ["tamu"], "3.4 1.6 5.9": ["nonwinning"], "9.3 1.9 9.1": ["kreteks"], "6.9 7.2 13.4": ["orchestrally"], "19.0 2.5 8.2": ["macromedia"], "8.5 2.3 9.3": ["neuroendocrinology"], "5.5 13.5 2.6": ["himto"], "2.9 8.4 14.0": ["dolomites"], "-2.1 1.2 5.1": ["asm"], "0.4 3.8 -0.5": ["approched"], "3.0 6.7 5.6": ["propsect"], "11.4 18.0 17.5": ["gubmint"], "9.8 24.3 12.8": ["darnit"], "4.8 7.7 -1.3": ["yeilded"], "10.3 -1.3 11.8": ["izzle"], "19.0 4.9 14.5": ["gamboled"], "25.1 19.3 17.8": ["sylphs"], "-9.9 19.7 -1.2": ["sentencer"], "20.3 9.0 22.5": ["sailer"], "7.2 5.6 12.4": ["scruffily"], "10.7 9.7 18.4": ["oj"], "14.7 9.3 22.7": ["mahonia"], "3.8 17.2 12.7": ["anfield"], "5.2 8.2 21.6": ["teeners"], "12.4 11.9 14.9": ["unpresentable"], "8.0 24.0 18.0": ["acedia"], "8.1 20.7 11.5": ["outdrives"], "-1.0 -0.1 11.5": ["nonmandated"], "6.8 -3.8 1.1": ["forthis"], "21.3 12.3 19.8": ["protuberant"], "3.6 7.0 10.4": ["baseplates"], "9.8 -2.2 38.8": ["bacalhau"], "16.0 18.5 20.7": ["redbacks"], "7.4 8.8 15.7": ["hopples"], "5.5 14.9 18.9": ["reggie"], "6.0 8.3 25.2": ["flouring"], "9.3 17.7 5.4": ["unmanipulated"], "8.8 8.6 15.4": ["musclecars"], "13.2 16.5 11.8": ["habituating"], "-2.0 11.8 0.0": ["insolubility"], "6.8 -1.2 12.5": ["deaccessioned"], "9.5 3.2 11.7": ["lightweig"], "4.8 10.7 11.4": ["millivolt"], "15.9 7.2 13.6": ["waterwheels"], "14.4 4.3 2.2": ["mediagenic"], "10.0 13.3 23.7": ["muscari"], "5.2 -4.9 8.7": ["superette"], "-2.2 18.0 2.5": ["soman"], "4.1 21.6 14.2": ["enmeshment"], "10.0 11.8 13.5": ["scrammed", "sesterces"], "0.2 19.7 27.3": ["surfmen"], "10.7 17.9 11.6": ["screamfest"], "13.3 2.2 35.8": ["camarones"], "16.2 5.3 12.2": ["faille"], "5.0 3.6 26.3": ["masi"], "-2.3 10.1 1.4": ["innappropriate"], "18.7 28.0 10.8": ["unnamable"], "6.0 0.0 6.9": ["headtube"], "-1.2 5.2 8.9": ["overdrafting"], "4.3 14.8 9.1": ["medicalizing"], "-2.6 9.9 8.7": ["oher"], "2.9 9.5 27.5": ["zests"], "8.2 0.0 13.3": ["bq"], "1.0 6.7 2.3": ["hemiparesis"], "3.6 -0.1 8.5": ["gael"], "0.9 5.7 2.0": ["shayari"], "23.1 9.9 17.6": ["builing"], "-3.3 14.5 -2.0": ["intoxilyzer"], "8.6 3.6 14.2": ["cephalic"], "3.9 22.3 5.7": ["somali"], "10.5 6.9 4.1": ["visio"], "12.3 13.0 11.7": ["shrilling"], "0.2 7.3 2.7": ["seizable"], "17.9 19.5 15.4": ["tranquillising"], "-4.2 5.0 13.3": ["patroned"], "4.5 11.3 7.6": ["ganas"], "5.5 18.3 13.7": ["gifter"], "8.3 11.8 11.3": ["unswept"], "5.9 3.3 8.5": ["bruno"], "14.5 1.1 3.0": ["theremins"], "5.8 1.7 9.1": ["webb"], "8.4 16.3 21.9": ["wristers"], "-1.0 -3.7 3.8": ["monitorship"], "6.5 3.1 16.7": ["hootenannies"], "-0.4 11.0 19.3": ["gunlock"], "2.9 9.7 12.8": ["opensides"], "12.0 6.6 6.1": ["sidetrip"], "-1.4 4.7 5.4": ["hyperprolactinemia"], "-4.2 3.1 2.1": ["newsjournal"], "20.9 11.7 11.3": ["engorging"], "15.1 14.9 11.2": ["pityingly"], "8.9 6.8 38.5": ["sugo"], "9.1 19.4 20.6": ["gobalobadingdong"], "-1.9 5.4 22.3": ["dolcetto"], "9.9 26.3 10.8": ["indomitably"], "17.0 10.7 2.5": ["komt"], "10.8 15.6 20.2": ["snubber"], "4.4 -0.6 10.6": ["hyo"], "2.9 10.8 -3.6": ["telexes"], "-1.4 2.2 1.1": ["chabad"], "-1.4 9.0 6.7": ["shortshop"], "5.1 -6.5 6.6": ["waxings"], "-4.1 -2.5 9.1": ["vicinage"], "9.6 11.3 18.8": ["festal"], "24.6 12.6 31.9": ["gummi"], "-2.0 4.9 10.1": ["woodburners"], "-1.8 16.6 0.9": ["remebered"], "12.3 10.9 33.8": ["baitcaster"], "-5.9 10.7 9.2": ["masl"], "13.4 8.5 7.2": ["zibotentan"], "13.5 7.7 5.9": ["trailling"], "-3.7 3.8 10.5": ["matty"], "4.2 6.5 -0.5": ["spyshots"], "13.2 9.1 16.0": ["dimply"], "8.9 4.5 2.9": ["yfrog"], "6.7 13.6 -3.4": ["motorpool"], "3.5 8.8 12.4": ["pizzicatos"], "8.8 8.9 19.8": ["rangolis"], "8.9 11.6 19.5": ["gisaeng"], "16.5 9.6 12.4": ["gobsmackingly"], "6.5 13.3 8.6": ["unncessary"], "6.1 11.8 6.5": ["recalibrations"], "4.1 24.6 3.3": ["cliquishness"], "2.9 4.4 0.4": ["matche"], "7.8 3.4 26.5": ["mamak"], "-2.6 10.5 6.4": ["polestar"], "-6.6 1.7 -0.9": ["transradial"], "6.7 6.9 11.4": ["costo"], "-9.0 7.3 7.3": ["grievant"], "7.1 25.2 8.8": ["enervate"], "4.3 3.6 1.6": ["anthropometry"], "14.0 -0.7 12.2": ["microservers"], "17.8 9.5 24.7": ["slipknot"], "17.7 9.3 13.0": ["burgher"], "2.1 7.9 11.2": ["deman"], "5.6 2.8 10.1": ["thumbdrives"], "26.4 6.3 2.6": ["partsmaker"], "0.8 3.2 10.5": ["methampetamine"], "-1.8 -0.5 4.7": ["transaminase"], "6.2 19.2 5.5": ["mishear"], "8.7 13.2 8.7": ["neovasculature"], "1.0 5.4 -6.7": ["decalred"], "2.3 9.8 6.8": ["pedia"], "-0.2 21.9 8.9": ["pushbacks"], "4.5 19.8 6.7": ["pauperisation"], "-5.4 5.9 13.0": ["nonqualifiers"], "10.4 7.0 18.8": ["planarians"], "13.7 2.2 40.9": ["bordelaise"], "9.0 25.9 6.8": ["facists"], "-1.5 7.7 8.9": ["bodyfat"], "7.6 24.7 19.6": ["mythologically"], "8.4 10.4 13.9": ["waling"], "4.8 12.3 4.5": ["spiritualized"], "13.0 7.7 15.5": ["sabor"], "6.4 5.9 21.0": ["primitivo"], "16.7 10.2 24.8": ["boxship"], "-3.7 8.9 3.4": ["prazosin"], "-3.4 11.2 5.9": ["dimeric"], "17.2 11.2 24.6": ["hoarfrost"], "19.9 10.6 18.0": ["upchucking"], "5.2 12.4 17.3": ["micropipette"], "5.2 3.6 7.4": ["transexuals", "alleg"], "7.4 -1.0 12.6": ["salud"], "6.2 22.1 13.2": ["troglodytic"], "4.3 -2.9 10.8": ["sedimentology"], "9.0 5.1 8.2": ["toothpowder"], "18.3 -1.2 9.8": ["ealry"], "16.6 22.4 7.0": ["collectivize"], "16.2 10.6 20.5": ["chlorotoxin"], "8.9 6.2 5.4": ["payrolling"], "-0.3 9.8 8.8": ["vidya"], "-3.4 11.8 3.6": ["alim"], "-2.1 4.6 6.0": ["nonaccruals"], "4.5 14.7 11.0": ["incertitude"], "-4.4 -5.7 -1.3": ["respirologist"], "2.5 9.0 11.9": ["sericitized"], "13.3 0.8 33.4": ["cep"], "12.3 22.5 6.3": ["cabalistic"], "1.9 11.7 10.0": ["afforested"], "4.1 10.9 14.2": ["schnide"], "8.7 6.6 1.6": ["techologies"], "3.8 11.8 9.8": ["bastman"], "6.8 1.6 11.9": ["afernoon"], "6.9 17.2 12.1": ["smoothbore"], "3.7 3.9 -2.8": ["bluesign"], "6.4 8.0 21.9": ["unmated"], "17.5 12.9 16.6": ["swains"], "1.9 8.9 12.9": ["jati"], "1.2 9.2 5.9": ["submucosal"], "-5.9 1.7 2.1": ["anticoagulated"], "18.8 9.5 24.3": ["quilled"], "12.0 17.4 35.6": ["blackfly"], "15.1 1.8 18.2": ["guitarron"], "18.9 15.3 28.8": ["sundew"], "-2.3 3.6 6.4": ["telecon"], "4.2 23.6 3.6": ["miscommunicating"], "23.4 14.7 12.1": ["farty"], "8.2 0.2 7.8": ["contiues"], "11.2 -0.3 3.9": ["microcurrent"], "6.2 13.4 5.6": ["dysfunctionally"], "-0.7 15.2 15.6": ["conversate"], "2.8 4.8 -8.5": ["aggreement"], "10.7 4.8 1.1": ["maisons"], "3.0 13.1 2.8": ["misfuelling"], "-2.1 9.0 9.5": ["vulval"], "-8.1 5.0 2.5": ["psychopharmacological"], "16.0 9.2 8.2": ["dazedly"], "7.8 15.2 7.2": ["sandbelt"], "9.9 17.6 5.3": ["hussein"], "13.6 18.8 21.7": ["spinkick"], "10.9 6.5 6.0": ["cingular"], "4.4 25.4 10.6": ["diplomatese"], "3.3 12.8 7.6": ["nanoindentation"], "7.2 29.2 1.9": ["zionism"], "1.0 4.9 4.4": ["oversizing"], "2.9 37.8 2.0": ["terrorisms"], "2.3 15.7 10.2": ["smallville"], "17.9 10.9 9.8": ["quangocrats"], "1.0 12.5 0.1": ["adulations"], "4.2 10.3 16.1": ["nonrepresentational"], "5.6 17.2 12.4": ["bodybag"], "10.8 25.6 14.1": ["predatorial"], "20.5 9.3 22.1": ["raggy"], "-1.2 10.9 14.0": ["pression"], "-0.5 5.4 23.0": ["alii"], "9.0 7.3 14.1": ["metropark"], "5.6 -1.5 21.3": ["yue"], "7.2 40.1 9.3": ["warmakers"], "12.1 13.0 31.2": ["fritillary"], "12.3 10.8 21.0": ["carousers"], "16.8 -1.8 11.4": ["tgp"], "7.2 5.7 17.4": ["forchlorfenuron"], "2.9 1.4 8.7": ["dure"], "5.2 12.5 11.3": ["newman"], "12.7 0.7 20.6": ["seaview"], "-1.0 4.5 16.7": ["polycarts"], "5.7 8.4 12.6": ["veinlet"], "0.4 13.6 3.8": ["unqualifiedly"], "-7.4 2.6 2.9": ["cummulative"], "13.0 19.3 20.1": ["possessively"], "7.6 -1.3 15.7": ["synthed"], "13.3 16.7 10.2": ["marketmakers"], "11.1 31.9 3.5": ["misleaders"], "-0.9 2.6 -3.0": ["membe"], "-3.6 -2.4 -0.8": ["fror"], "7.3 19.8 2.1": ["forswears"], "9.4 6.2 4.2": ["lineside"], "-1.0 0.3 4.1": ["sceduled"], "19.1 13.8 4.4": ["wirless"], "12.5 4.4 17.7": ["purlins"], "-3.3 4.5 1.5": ["oathtaking"], "11.5 11.7 16.8": ["pennyroyal"], "5.4 5.5 7.5": ["offcourse"], "10.7 5.7 -6.7": ["acompany"], "6.0 24.9 12.8": ["griever"], "0.9 -2.9 4.8": ["theproject"], "16.7 13.0 16.3": ["hoik"], "11.7 23.5 10.5": ["pwning"], "10.9 22.0 8.1": ["tenebrous"], "-4.7 3.9 2.8": ["atheltic"], "3.9 4.9 8.7": ["vhs"], "2.1 3.9 12.6": ["patra"], "5.1 5.8 10.3": ["freehouse"], "8.0 14.2 18.8": ["kouprey"], "8.5 4.3 3.5": ["archiver"], "10.1 18.7 11.4": ["sloggers"], "15.4 13.1 34.1": ["rattletraps"], "6.2 15.4 7.1": ["sloan"], "7.6 7.5 11.9": ["losts"], "13.5 7.3 15.6": ["pagent"], "11.5 11.7 30.4": ["aspidistra"], "7.7 31.5 11.2": ["srilankan"], "3.0 -2.5 8.5": ["unbeatably"], "13.0 11.9 35.8": ["waterfowls"], "23.0 10.8 33.7": ["ostracods"], "15.5 0.6 -0.6": ["thethird"], "1.3 13.7 9.0": ["sabermetrician"], "8.8 18.7 13.8": ["rediculously"], "9.3 5.2 29.3": ["johnboats"], "5.5 1.4 21.8": ["muga"], "15.9 37.4 5.8": ["mutantkind"], "4.1 6.9 16.7": ["watter"], "8.5 6.0 0.9": ["previewer"], "1.7 6.0 13.4": ["haris"], "-5.5 10.7 5.0": ["intepretation"], "2.2 8.4 1.5": ["reductant"], "8.0 18.8 -3.4": ["lionise"], "14.1 11.0 16.9": ["helmut"], "9.4 11.6 14.6": ["foghornleghorn"], "-8.8 12.9 -3.4": ["conviced"], "2.8 12.3 14.1": ["ofthose"], "1.2 -1.4 1.6": ["acharyas"], "19.1 7.9 13.2": ["horribilis"], "15.8 1.0 10.3": ["pranged"], "8.8 8.9 14.5": ["toxicosis"], "12.0 6.7 12.9": ["quaaludes"], "13.6 12.1 6.2": ["anterooms"], "10.2 9.7 17.4": ["stretchmarks"], "18.0 4.2 14.0": ["clubbie"], "5.3 15.0 8.8": ["separationists"], "0.1 15.0 9.7": ["fragmental"], "1.8 25.1 8.6": ["crisises"], "9.6 4.9 3.8": ["backheeling"], "8.9 19.4 10.1": ["deloused"], "8.5 11.6 15.5": ["dithery"], "22.9 2.3 12.5": ["siz"], "21.6 4.8 4.1": ["holographs"], "3.2 18.0 12.1": ["indemnitee"], "20.6 8.7 16.1": ["hoicked"], "10.1 4.8 0.8": ["wsj"], "7.5 1.4 5.3": ["otras"], "-9.3 7.4 0.4": ["nondependent"], "-7.4 6.8 -5.7": ["promotees"], "3.1 4.1 14.3": ["bitchfest"], "7.4 1.6 -4.8": ["microform"], "5.6 2.8 7.7": ["horst"], "4.6 22.0 15.8": ["strats"], "16.3 10.8 4.1": ["circuiting"], "9.6 8.0 14.4": ["mypure"], "13.5 15.7 12.2": ["countryfolk"], "11.3 7.3 9.7": ["legistlation"], "8.3 21.6 13.2": ["extricates"], "18.6 18.3 18.8": ["greyest"], "-9.7 -3.7 1.3": ["informatin"], "4.1 9.2 2.2": ["psychoacoustics"], "8.5 22.8 3.6": ["revolutionarily"], "26.7 3.5 24.0": ["teacake"], "2.9 -6.6 -0.9": ["alumus"], "0.6 -3.6 -1.0": ["hopital"], "7.2 12.8 8.1": ["militaire", "fleetly"], "13.6 7.5 8.8": ["contructed"], "-7.7 -3.5 -3.2": ["psc"], "9.2 4.5 22.8": ["forro"], "7.3 14.4 12.4": ["basophils"], "9.7 5.7 19.4": ["lehngas"], "15.5 11.3 15.4": ["homeliest"], "5.9 17.0 2.0": ["possibe"], "9.1 8.4 16.1": ["tumescence"], "16.2 12.2 17.0": ["buckin"], "2.4 11.5 8.0": ["dejudder"], "11.9 18.4 10.2": ["exoduses"], "-3.5 5.1 13.6": ["topness"], "4.9 3.8 4.0": ["alleygates"], "4.6 7.0 1.5": ["freewheelin"], "0.9 4.0 7.6": ["differents"], "-0.3 -2.1 2.7": ["dichloromethane"], "1.1 21.5 7.0": ["worketh"], "4.6 16.4 11.2": ["dunum"], "10.3 19.2 14.1": ["shoting"], "12.1 10.8 11.3": ["weatherstrip"], "6.7 7.4 4.8": ["czech"], "15.9 9.3 4.4": ["lnk"], "-0.1 16.7 15.4": ["paceline"], "17.8 16.4 7.8": ["oleophobic"], "-2.7 23.3 7.6": ["poltics"], "2.2 7.7 9.8": ["personne"], "10.8 8.7 5.6": ["precipitators"], "0.5 13.5 2.5": ["ancien"], "6.8 7.5 13.3": ["bougie"], "-0.6 20.7 29.4": ["culex"], "-4.6 -4.7 -0.4": ["noncity"], "8.0 17.1 5.0": ["immuned"], "10.6 -0.3 -2.9": ["plansto"], "6.5 0.4 16.8": ["psaltery"], "1.8 9.2 14.4": ["twa"], "13.4 14.5 10.0": ["unfading"], "1.1 3.1 11.8": ["reexport"], "12.4 5.9 26.2": ["hairlike"], "12.5 9.1 13.8": ["facetted"], "9.3 15.8 10.1": ["fireguards"], "8.1 7.0 13.4": ["crawford"], "5.5 9.6 13.8": ["bynum"], "0.7 -4.3 6.7": ["sociolinguistics"], "15.4 11.1 4.6": ["sym"], "6.3 2.4 9.1": ["mogas"], "3.9 3.9 13.9": ["geoparks"], "2.3 8.2 4.2": ["dharamshala"], "1.0 6.1 28.0": ["kawa"], "14.4 0.1 5.7": ["wokers"], "15.9 7.8 2.8": ["reputationally"], "20.1 11.8 31.3": ["hootchie"], "8.7 10.8 6.5": ["crisi"], "6.0 9.7 13.9": ["isolette"], "17.6 9.1 12.4": ["lappie"], "-3.1 -4.4 4.6": ["decatherms"], "4.3 13.7 14.1": ["tmittelstaed"], "7.8 12.4 -3.5": ["nternet"], "18.7 1.5 9.0": ["sterilises"], "4.4 2.2 5.5": ["therewas"], "17.5 6.3 42.3": ["shumai"], "4.9 5.5 15.8": ["weiss"], "9.0 0.9 12.5": ["kampo"], "9.0 14.6 8.8": ["framings"], "1.2 7.1 2.6": ["baroreflex"], "12.7 17.2 1.5": ["subsidiarisation"], "-19.0 19.9 -1.4": ["detainable"], "5.2 10.5 16.5": ["ejidos"], "8.9 19.8 12.5": ["uncoverable"], "6.0 11.1 14.9": ["exportations"], "20.2 -0.7 3.5": ["reprots"], "19.4 13.7 4.7": ["asit"], "11.0 9.9 15.1": ["concavity"], "2.8 2.4 20.1": ["rewash"], "13.3 10.1 14.9": ["swage"], "2.4 9.7 14.6": ["unbelieveably"], "9.5 10.5 7.2": ["cramdowns"], "11.6 6.7 17.6": ["kwila"], "-0.0 4.3 4.6": ["wrk"], "14.1 5.6 9.0": ["mouldable"], "-6.9 8.6 0.8": ["kiruv"], "11.0 2.8 4.1": ["instutions"], "2.3 10.1 9.4": ["prothioconazole"], "4.0 12.8 10.9": ["tuple"], "22.0 -2.4 5.2": ["utives"], "2.3 2.8 9.4": ["ethologist"], "4.0 17.3 10.5": ["skils"], "5.9 3.3 11.4": ["soundalikes"], "-2.0 -6.3 11.5": ["lactations"], "-7.1 9.5 13.8": ["dene"], "18.1 17.7 11.7": ["wobblies"], "2.8 9.9 12.5": ["normaly"], "13.3 15.0 11.1": ["downbeats"], "7.1 4.2 2.4": ["rebodied"], "10.4 15.4 11.4": ["masturbators"], "5.0 14.2 5.6": ["medicab"], "9.6 7.7 6.5": ["vulgarized"], "-4.7 -0.8 5.2": ["adapalene"], "8.2 -3.2 9.1": ["summmer"], "15.2 11.1 17.3": ["aaaah"], "11.9 5.7 0.6": ["pinless"], "18.3 12.4 13.7": ["quasicrystal"], "6.9 11.3 10.1": ["seaching"], "13.8 9.8 26.3": ["knapping"], "2.6 3.4 18.0": ["walsh"], "0.4 6.3 5.7": ["misapplications"], "5.3 3.5 12.2": ["parador"], "4.2 12.1 25.2": ["thymes"], "4.2 17.3 12.0": ["nondominant"], "9.2 13.0 9.6": ["unstrap"], "-7.9 4.7 2.1": ["yearsold"], "6.2 2.0 10.9": ["laat"], "8.6 14.3 15.1": ["expectorate"], "10.4 16.2 2.2": ["humilating"], "5.1 16.4 6.6": ["stabalize"], "12.4 6.1 13.6": ["skal"], "7.2 7.2 22.5": ["sugarcanes"], "2.8 2.3 1.7": ["lycee"], "0.8 8.8 7.3": ["realtively"], "5.9 1.5 16.5": ["bankbooks"], "5.8 4.6 15.7": ["vero"], "18.5 5.4 17.7": ["squeezers"], "21.8 12.2 15.5": ["microcapsule"], "-1.4 8.3 19.1": ["detasseling"], "11.7 0.4 10.3": ["belgium"], "11.1 14.8 10.7": ["evista"], "16.6 8.1 15.6": ["lochside"], "12.2 21.6 16.0": ["knacker"], "18.2 -3.5 10.7": ["ultrasuede"], "12.7 9.3 7.5": ["withhis"], "3.5 7.4 -4.0": ["tarnishment"], "25.2 21.0 17.4": ["goodfellas"], "13.2 10.9 6.2": ["quavers"], "0.8 18.7 10.1": ["punctiliously"], "6.1 18.4 12.2": ["iwas"], "8.6 11.1 19.6": ["fellahs"], "11.6 21.6 10.3": ["hollowly"], "1.3 15.2 8.7": ["azzurri"], "-2.6 19.0 -2.6": ["dialoging"], "2.5 1.7 9.2": ["issa"], "8.2 4.3 5.1": ["perampanel"], "1.4 3.4 22.0": ["raisiny"], "4.0 1.4 11.9": ["lexington"], "16.1 11.4 19.5": ["vanitas"], "1.4 28.9 8.3": ["idolater"], "-2.0 7.2 14.3": ["mangyayari"], "0.7 3.6 11.6": ["abogado"], "6.1 1.0 17.3": ["vienna"], "3.4 -2.5 3.1": ["budgetted"], "13.1 13.0 27.5": ["hoya"], "7.7 5.4 5.4": ["radiotherapeutics"], "-6.9 10.0 -3.9": ["declarants"], "14.2 8.3 0.9": ["mattporterwd"], "6.2 6.7 5.8": ["vook"], "0.2 15.6 11.7": ["irrigable"], "-13.2 10.6 8.7": ["aquatinted"], "-3.0 17.5 1.1": ["caveated"], "1.4 14.2 12.5": ["blocklists"], "9.8 3.0 14.0": ["luc"], "7.1 12.4 17.0": ["paleochannel"], "-6.6 0.8 4.4": ["lumbosacral"], "20.0 15.6 18.2": ["bullheading"], "1.9 7.4 14.1": ["maro"], "13.8 -1.1 10.2": ["hexa"], "4.1 19.0 12.2": ["acinetobacter"], "9.8 9.9 14.1": ["quadrella"], "10.5 6.9 10.0": ["nort"], "8.5 5.7 5.0": ["svn"], "3.1 5.1 17.2": ["tatlong"], "4.8 21.9 5.6": ["invidiously"], "4.4 8.1 8.9": ["athens"], "7.3 4.2 16.6": ["serapes", "jonny"], "18.8 6.9 0.7": ["thatwas"], "5.0 17.0 3.4": ["minorites"], "-4.9 0.6 2.2": ["tetracaine"], "-3.6 22.4 12.5": ["tragical"], "1.3 12.9 17.2": ["preprogram"], "13.0 5.7 10.2": ["bahrain"], "3.0 3.6 7.0": ["phasic"], "2.6 5.9 5.0": ["modbook"], "3.6 13.1 17.6": ["altitudinal"], "10.9 0.7 7.6": ["nanocar"], "13.6 4.3 8.9": ["lovenest"], "8.8 14.4 21.3": ["growthers"], "10.9 9.1 4.1": ["bookstand"], "16.2 2.7 10.2": ["ellipsoidal"], "4.9 24.2 15.6": ["yomp"], "19.7 12.3 25.0": ["squiggled"], "20.4 14.5 19.8": ["muscley"], "2.1 9.8 3.4": ["ropeable"], "-3.0 14.2 7.9": ["solemnities"], "18.1 16.2 25.2": ["placoderms"], "1.1 5.8 16.1": ["aliquots"], "-3.1 14.2 8.5": ["kairos"], "5.5 -2.3 10.5": ["gwaith"], "10.0 10.2 16.5": ["aquaplane"], "7.1 15.6 2.8": ["disobliging"], "12.3 10.5 13.8": ["allee"], "7.9 8.2 8.6": ["corazon"], "5.5 14.9 8.2": ["attemping"], "-0.3 8.5 5.2": ["mrem"], "2.4 3.3 9.6": ["tarriff"], "1.6 7.2 10.9": ["phyllic"], "1.6 15.6 0.8": ["negotation"], "-6.7 -4.4 5.1": ["recitalists"], "7.6 5.6 2.0": ["formated"], "9.0 5.2 10.9": ["daryl"], "12.2 9.8 3.9": ["robotised"], "20.9 32.3 8.3": ["goosestep"], "11.9 11.9 11.5": ["hahahahahaha"], "0.7 12.8 17.4": ["deltamethrin"], "15.5 21.6 14.9": ["furriest"], "19.5 19.8 12.8": ["crummiest"], "8.9 11.4 11.2": ["tite"], "16.6 7.6 16.4": ["didja"], "4.9 4.6 21.8": ["buta"], "7.7 19.8 3.3": ["occultic"], "0.6 12.9 10.2": ["illa"], "13.4 13.5 31.2": ["unbuttered"], "5.4 15.1 9.5": ["geophysically"], "-2.7 3.6 19.5": ["mortis"], "5.2 10.6 4.5": ["partes"], "11.8 21.9 10.3": ["bareknuckle"], "-1.3 7.9 2.1": ["millionare"], "-4.3 13.5 15.6": ["usdjpy"], "6.4 16.8 10.1": ["unpeopled"], "9.4 9.8 12.5": ["bellydancers"], "-5.7 15.8 2.3": ["excatly"], "14.1 10.9 12.2": ["riving"], "-5.5 5.3 11.8": ["histiocytosis"], "-4.0 8.3 12.4": ["telomeric"], "6.8 15.4 16.6": ["propitiated"], "10.0 0.4 5.5": ["platfrom"], "7.9 7.4 6.5": ["streetable"], "16.1 9.5 8.6": ["infrasonic"], "4.8 9.3 16.2": ["simmons"], "8.3 16.8 4.9": ["epiphenomenon"], "13.8 21.3 18.3": ["sleepyheads"], "9.8 28.6 7.8": ["flatout"], "5.2 23.7 13.0": ["armas"], "5.9 13.3 0.0": ["threatned"], "8.7 1.7 24.0": ["kui"], "0.6 6.3 6.6": ["plunkings"], "-0.7 8.8 7.1": ["concertgoing"], "10.6 8.8 20.6": ["freddy"], "13.1 9.4 12.4": ["worksurface"], "6.2 -5.8 -0.4": ["introducted"], "9.8 10.9 31.4": ["appletini"], "-1.0 11.5 17.0": ["longstick"], "8.0 4.6 -3.1": ["offiicials"], "1.5 13.5 8.8": ["quotability"], "11.6 2.6 11.4": ["excelsis"], "9.0 11.9 11.8": ["surya"], "10.6 8.6 7.0": ["cringey"], "10.6 9.2 13.3": ["aeolian"], "6.0 14.6 26.6": ["epiphytic"], "9.2 11.5 8.6": ["surpisingly"], "-1.6 8.2 2.0": ["weder"], "14.5 8.3 12.7": ["mambos"], "2.9 2.0 3.3": ["anmd"], "7.7 3.8 11.9": ["asl"], "11.9 -6.7 10.0": ["proprieter"], "13.9 8.6 14.9": ["allez"], "-4.3 9.7 2.0": ["sufficing"], "12.4 19.0 9.7": ["wonted"], "16.2 16.3 23.7": ["mouflon"], "-2.8 0.0 -8.7": ["intouch"], "1.5 -1.9 8.7": ["ibooka"], "-0.9 2.8 12.7": ["torticollis"], "-1.7 15.5 14.3": ["workwise"], "9.9 3.3 4.1": ["libpng"], "1.1 21.6 7.7": ["indispensably"], "8.2 10.5 10.5": ["airtightness"], "13.4 4.2 14.1": ["minitower", "hakas"], "-2.1 1.5 9.2": ["rifapentine"], "-10.6 11.7 -3.2": ["responsibles"], "12.0 3.1 12.6": ["fros"], "6.3 3.1 15.7": ["hamfest"], "-2.4 0.9 -5.9": ["reclass"], "3.4 2.3 15.1": ["colluvial"], "9.6 -9.8 7.2": ["royalities"], "3.1 9.5 9.2": ["lineworkers"], "23.7 12.6 22.6": ["chittering"], "26.0 3.2 18.3": ["polyresin"], "4.4 10.1 30.9": ["zaatar"], "14.0 3.7 11.1": ["moil"], "1.8 8.6 17.4": ["oru"], "21.9 11.7 19.5": ["ludo"], "9.4 6.1 22.8": ["toby"], "15.8 1.9 24.3": ["vermeil"], "2.0 9.7 15.9": ["etceteras"], "12.5 4.0 23.2": ["mua"], "7.2 25.4 9.2": ["antipode"], "8.3 14.3 11.6": ["campiest"], "16.3 8.3 16.9": ["choppin"], "1.0 4.8 7.6": ["overtemperature"], "3.4 2.3 3.0": ["tearsheets"], "-3.2 14.4 4.5": ["yagya"], "5.3 0.5 19.9": ["destocked"], "3.0 6.3 23.0": ["candlepin"], "16.7 -2.4 35.2": ["roquefort"], "12.4 3.2 7.7": ["flipcharts"], "0.3 5.5 10.5": ["kontra"], "2.9 1.5 12.0": ["glucoside"], "4.8 11.2 1.3": ["sutradhar"], "1.3 6.6 13.2": ["illite"], "-1.6 -0.8 6.3": ["stad"], "9.7 6.1 6.0": ["houshold"], "21.2 7.9 20.1": ["calabashes"], "16.2 10.9 -2.4": ["compaq"], "5.4 16.6 -2.0": ["detered"], "-1.4 1.5 9.8": ["nephrolithiasis"], "5.3 8.5 12.5": ["spendin"], "-2.0 -18.1 7.5": ["sixmonths"], "4.4 18.7 0.7": ["indivduals"], "6.9 10.2 0.0": ["negotiatons"], "3.9 11.7 14.0": ["heartful"], "19.4 5.8 18.1": ["doubletake"], "14.8 9.3 12.6": ["finallists"], "5.4 4.4 1.7": ["fastrack"], "4.4 13.7 14.0": ["variablespanner"], "16.0 12.6 25.7": ["boxfish"], "3.4 8.3 16.6": ["mays"], "-4.9 15.0 -1.0": ["assiduity"], "13.8 10.5 6.0": ["mimicing"], "7.0 19.9 21.8": ["easting"], "9.2 11.1 1.4": ["enshrinee"], "9.7 2.1 16.5": ["flocculent"], "2.5 9.9 8.9": ["utile"], "11.0 24.0 29.2": ["bagworm"], "9.8 5.2 9.7": ["multiway"], "-6.0 8.0 6.3": ["cedant"], "10.9 7.0 33.2": ["crudite"], "8.3 2.0 6.0": ["rakings"], "2.4 10.3 7.5": ["randomizes"], "1.8 13.9 -0.6": ["antifog"], "20.9 15.0 15.4": ["chirrup"], "15.7 11.0 15.9": ["neckless"], "-4.3 8.8 10.2": ["urbanicity"], "9.3 11.0 13.2": ["horndogs"], "12.6 13.2 19.9": ["ponderousness"], "9.6 15.2 8.9": ["jerkoff"], "0.5 17.9 4.1": ["unsay"], "12.0 4.2 8.4": ["geekfest"], "16.8 6.9 18.5": ["ironware"], "7.0 -2.8 -2.6": ["sanef"], "7.2 21.1 6.4": ["racisim"], "4.2 14.8 2.9": ["phyiscal"], "-11.1 4.1 7.8": ["committeewomen"], "17.9 26.9 2.7": ["underworlds"], "-6.4 7.5 -2.2": ["incharges"], "5.2 8.2 27.1": ["roadkills"], "-7.1 8.9 -1.0": ["sotalol"], "2.5 16.7 11.2": ["blindsight"], "-0.4 16.7 13.1": ["politicals"], "-1.8 -16.4 3.6": ["contrat"], "-2.6 18.5 4.1": ["incumbants"], "8.9 18.8 4.9": ["memorialising"], "17.9 12.6 12.9": ["shadowless"], "-2.8 16.7 3.9": ["irenic"], "14.4 -3.5 4.1": ["manuf"], "-4.5 10.5 3.0": ["invaluably"], "0.1 8.1 -1.5": ["assulted"], "1.5 1.4 7.5": ["seatposts"], "-2.3 9.1 8.9": ["alap"], "16.0 6.8 7.4": ["loges"], "3.9 9.6 6.9": ["dayrooms"], "6.7 18.3 -0.0": ["epecially"], "18.2 9.0 12.4": ["keycaps"], "3.4 6.4 17.3": ["pablo"], "6.6 17.1 0.5": ["explantion"], "12.6 9.8 11.9": ["aguardiente"], "0.7 0.3 9.1": ["pmtoday"], "20.0 5.7 19.5": ["shitzu"], "3.0 27.1 9.3": ["seperatist"], "9.9 17.1 33.2": ["houbara"], "6.5 7.0 18.8": ["toxaphene"], "9.4 18.2 3.5": ["gradiometer"], "-4.7 3.5 -2.0": ["homologate"], "14.7 11.1 5.2": ["nytimes"], "20.6 6.0 5.9": ["tobuy"], "4.0 4.9 7.0": ["hookey"], "-0.0 13.8 -8.6": ["systemised"], "15.1 28.2 2.1": ["hostilely"], "23.8 5.2 -3.9": ["copmany"], "7.7 18.8 17.7": ["spitted"], "11.9 1.6 4.1": ["polytetrafluoroethylene"], "11.1 12.3 17.9": ["crotchless"], "2.9 15.6 3.3": ["priveledge"], "1.9 7.6 6.2": ["softswitching"], "-2.2 -2.7 4.9": ["acarbose"], "8.5 4.2 10.1": ["ecnomic"], "-2.2 -0.1 4.4": ["videoblogs"], "0.1 -2.2 11.5": ["relending"], "26.1 6.4 21.9": ["triton"], "7.8 9.3 13.5": ["everythin"], "-1.4 3.8 7.5": ["verik"], "5.3 9.7 2.5": ["electrodynamics"], "13.7 -1.0 -4.6": ["webstores"], "11.7 5.7 3.6": ["photoacoustic"], "-0.8 2.3 -5.1": ["invoved"], "6.9 6.6 7.4": ["octagenarian"], "12.7 9.9 13.4": ["mesmerisingly"], "0.9 1.5 9.1": ["vinpocetine"], "4.7 11.0 11.3": ["niner"], "25.9 18.4 43.4": ["boatside"], "7.7 11.8 -4.6": ["unconfirmable"], "11.9 -0.6 10.6": ["mirco"], "-7.8 11.7 3.3": ["misapplies"], "1.7 1.9 4.3": ["tricuspid"], "4.4 6.3 -7.0": ["connexions"], "1.2 12.7 5.8": ["quinone"], "18.4 7.1 9.0": ["minipark"], "11.4 9.5 18.3": ["taxonomically"], "1.0 14.2 5.3": ["audiogram"], "4.9 12.6 12.9": ["gerard"], "-9.4 23.2 7.3": ["concerend"], "14.8 11.4 12.7": ["phishy"], "10.4 18.5 8.2": ["bidoun", "comfortless"], "5.2 16.9 10.1": ["typer"], "19.2 2.9 15.7": ["trommel"], "25.0 9.9 3.5": ["antirust"], "-1.0 5.6 3.0": ["tophi"], "-0.8 -1.9 6.4": ["ofthree"], "12.6 26.6 12.6": ["lifeforce"], "-8.0 -1.2 4.5": ["gation"], "13.2 24.0 8.4": ["instrumentalism"], "12.6 6.0 25.9": ["maguey"], "9.9 9.5 11.6": ["mezuza"], "9.0 7.9 6.4": ["mintes"], "12.9 12.4 51.9": ["sculpins"], "17.7 35.0 13.2": ["signaler"], "-0.3 10.6 7.5": ["radezolid"], "-4.0 10.9 4.1": ["resettlers"], "8.7 2.5 5.2": ["stokvel"], "-2.1 4.0 0.4": ["endocrinological"], "3.6 3.8 33.8": ["keropok"], "19.4 7.8 9.4": ["earholes"], "11.4 15.9 15.4": ["hardcase"], "6.1 12.7 3.8": ["sry"], "8.0 7.8 32.2": ["bassin"], "1.0 5.3 28.1": ["whio"], "18.4 9.9 3.1": ["ffff"], "0.3 -3.9 18.0": ["maui"], "-1.1 2.2 10.5": ["qty"], "0.4 1.5 26.4": ["tibs"], "2.0 13.4 12.3": ["dumbspammers"], "3.9 9.1 14.5": ["leukoplakia"], "3.7 7.7 8.4": ["shipset"], "6.8 -0.2 -4.0": ["dormroom"], "14.3 21.8 10.3": ["deviltry"], "8.1 12.2 14.2": ["unmodulated"], "16.3 12.1 12.4": ["gadgeteers"], "-0.6 2.2 19.1": ["pickins"], "0.3 0.4 2.4": ["outdooring"], "15.9 3.8 2.2": ["untethers"], "5.0 22.9 17.6": ["bodyshots"], "25.3 10.6 12.8": ["bespeckled"], "6.3 7.9 20.4": ["drumlins"], "2.8 -0.8 4.7": ["discusss"], "13.3 19.2 6.9": ["denominating"], "-0.2 3.9 4.3": ["disapply"], "5.4 3.0 5.1": ["rnd"], "6.1 4.5 17.5": ["sundance"], "-2.0 7.8 8.6": ["asssists"], "8.5 3.9 20.2": ["dichlorvos"], "1.3 -3.5 9.4": ["appoximately"], "-9.1 3.9 4.0": ["genral"], "3.9 -4.9 4.0": ["readathon"], "3.0 8.9 7.9": ["contused"], "10.6 8.7 8.7": ["theit"], "7.8 1.4 17.0": ["lous"], "-8.0 10.5 6.1": ["assemblymembers"], "-5.4 15.8 10.5": ["stepmoms"], "1.9 7.7 9.9": ["fusionist"], "-2.6 6.2 0.1": ["editoral"], "8.4 2.5 -1.5": ["marcoms"], "-5.8 -2.3 9.2": ["reen"], "-2.0 27.3 -0.8": ["neutralist"], "15.1 22.5 19.8": ["nagas"], "5.0 34.4 5.0": ["infighter"], "-11.8 18.4 4.7": ["unapparent"], "11.2 19.8 12.6": ["cosmologies"], "-6.9 11.8 9.1": ["chassidim"], "11.0 7.8 8.3": ["farside"], "5.7 9.6 15.7": ["dags"], "-1.9 13.4 12.3": ["kriging"], "8.6 -4.3 6.2": ["printery"], "9.2 11.4 16.1": ["dalang"], "7.4 23.4 6.1": ["vivifying"], "-0.3 -0.0 8.3": ["hexavalent"], "0.6 -1.5 11.8": ["carmustine"], "8.2 15.1 25.2": ["overbeat"], "-3.0 3.4 10.3": ["antipyretics"], "2.2 16.4 14.0": ["parranda"], "1.4 1.4 10.8": ["hematopathology"], "-4.0 13.2 1.8": ["nonspecialists"], "6.5 11.2 14.7": ["dustiness"], "12.6 19.8 28.8": ["sharptails"], "12.9 2.6 17.8": ["chuckwagons"], "7.4 3.8 5.5": ["problemas"], "-9.9 3.4 16.7": ["belg"], "-1.4 -1.4 19.0": ["vels"], "17.5 14.1 27.8": ["grabbling"], "7.1 7.0 11.4": ["estaba"], "3.0 -0.6 2.0": ["transformerless"], "3.2 15.4 4.4": ["propell"], "4.7 -3.4 16.7": ["oxycotin"], "3.4 21.5 3.1": ["interdependently"], "7.4 10.6 11.1": ["eyecandy"], "18.5 12.8 50.9": ["silversides"], "11.0 1.4 17.8": ["talo"], "16.0 14.3 28.5": ["centreboard"], "9.3 5.1 12.1": ["homogenizer"], "-10.0 4.2 10.8": ["emini"], "6.2 9.3 15.0": ["avy"], "8.4 5.7 14.8": ["dacitic"], "11.2 6.1 26.1": ["tikki"], "3.4 8.4 5.8": ["laropiprant"], "-7.7 19.2 0.5": ["nonrecognition"], "11.0 -0.9 33.4": ["caldo"], "9.1 9.5 44.7": ["kokes"], "7.0 4.8 8.8": ["biobusiness"], "3.5 -3.1 6.8": ["dehydroepiandrosterone"], "15.4 9.4 25.0": ["sundews"], "3.6 2.3 21.6": ["chappatis"], "15.7 8.0 9.4": ["yarning"], "-3.8 12.6 10.1": ["nonsworn"], "-2.2 1.5 6.0": ["reticulocytes"], "-0.3 7.6 2.7": ["passu"], "8.4 28.6 13.5": ["ransome"], "-8.1 10.1 2.3": ["deaconate"], "4.6 17.8 6.5": ["jerusalem"], "15.1 11.6 5.8": ["typers"], "7.5 12.5 -3.1": ["radiogram"], "25.7 7.4 9.0": ["velocipede"], "16.0 4.4 -1.3": ["eyeware"], "2.2 17.8 11.3": ["vomitus"], "-2.4 1.5 8.6": ["lana"], "13.7 7.6 16.2": ["savin"], "13.0 19.1 8.9": ["etheric"], "4.7 0.7 13.5": ["figues"], "12.6 6.9 12.2": ["moldmaking"], "12.8 -4.9 -0.9": ["sterilisers"], "6.0 6.0 -3.0": ["tly"], "10.9 -4.2 5.3": ["informatique"], "11.3 3.1 20.7": ["kuda"], "-7.0 -1.1 6.7": ["ott"], "3.9 2.1 2.4": ["oxygenator"], "7.1 2.3 9.2": ["kahani"], "12.0 4.6 18.3": ["cero"], "3.9 -1.2 7.7": ["addas"], "3.1 18.0 3.5": ["frei"], "18.2 16.0 5.4": ["wondergoal"], "-2.6 16.4 4.1": ["subagents"], "-6.6 -4.7 2.4": ["inal"], "9.6 3.8 8.9": ["solanezumab"], "2.1 8.5 17.2": ["ramadan"], "8.3 4.8 4.6": ["beena"], "2.1 4.9 7.0": ["arthrosis"], "9.5 9.7 15.0": ["rotoscope"], "0.2 21.7 12.3": ["apoligize"], "-0.5 -1.6 -4.5": ["releas"], "17.9 27.1 14.9": ["viewscreen"], "3.3 9.5 12.4": ["kunda"], "9.9 13.8 6.1": ["disincentivize"], "6.3 5.2 4.4": ["nattered"], "-3.3 5.4 8.1": ["ergocalciferol"], "14.6 9.5 6.7": ["xoom"], "6.6 3.5 10.7": ["kaiso"], "-7.3 6.8 -0.6": ["upzone"], "1.6 7.1 9.3": ["oligomerization"], "6.7 4.5 7.1": ["farnesene"], "12.4 4.9 16.8": ["texturising"], "20.3 7.7 23.3": ["lazes"], "10.5 15.8 21.8": ["weeders"], "19.5 8.4 4.7": ["minicams"], "0.2 -5.4 3.4": ["rescore"], "12.7 -0.2 -2.3": ["degasification"], "6.2 26.3 12.3": ["doubleteam"], "2.5 4.5 3.1": ["terme"], "16.2 8.8 13.1": ["tweenie"], "-1.2 2.9 4.8": ["treatability"], "7.8 17.5 9.3": ["newsweek"], "-1.8 7.5 16.0": ["cerumen"], "8.7 18.2 15.0": ["lamebrain"], "-6.6 6.9 2.7": ["hypermobility"], "19.9 8.0 19.2": ["jap"], "1.3 19.2 12.2": ["alternatingly"], "2.2 4.6 6.1": ["hyperemia"], "16.7 38.5 13.0": ["bogyman"], "15.4 9.3 2.0": ["proddings"], "-9.4 5.8 2.1": ["reinfarction"], "4.4 12.1 5.2": ["intrapreneurs"], "12.8 15.4 5.5": ["dumbphones"], "9.6 25.9 7.1": ["ignorants"], "7.7 9.9 15.5": ["daggering", "hattitude"], "-2.5 1.0 0.6": ["reimprisonment"], "0.7 9.1 0.7": ["extradiction"], "6.5 11.0 13.4": ["indiepop"], "-1.2 16.4 -1.3": ["outcoaching"], "17.4 13.3 3.5": ["dematerializing"], "-5.0 5.8 10.4": ["teamhigh"], "5.8 5.8 37.1": ["belacan"], "14.5 5.2 -1.6": ["refocussing"], "13.3 5.3 17.1": ["coronas"], "3.7 4.0 16.6": ["stylista"], "-3.8 29.0 0.8": ["battallion"], "16.1 5.4 17.2": ["kegging"], "-0.5 6.4 12.0": ["diplexers"], "11.4 7.1 27.7": ["granitas"], "1.5 2.3 8.1": ["temas"], "9.8 0.3 6.2": ["transmodus"], "-6.3 4.3 4.4": ["multigigabit"], "1.6 15.6 -2.3": ["refounded"], "9.0 2.5 1.1": ["energyefficient"], "6.9 12.5 14.2": ["amphioxus"], "-6.0 6.0 3.3": ["undercar"], "-0.9 16.2 1.0": ["togehter"], "13.1 16.1 11.9": ["jacker"], "11.4 8.7 11.9": ["tootin"], "8.6 4.9 18.9": ["shikumen"], "15.7 0.5 9.5": ["granulator"], "1.9 3.1 5.0": ["sait"], "-2.6 17.4 3.4": ["clutchness"], "12.1 34.5 8.4": ["iraqis"], "11.3 -1.9 16.9": ["wholefood"], "17.3 14.8 17.0": ["omigosh"], "4.6 15.1 12.3": ["addage"], "4.5 14.0 13.6": ["dropshippers"], "15.4 9.3 11.4": ["wallas"], "-7.4 16.3 9.2": ["herpesviruses"], "15.8 6.9 4.7": ["bioinnovation", "xine"], "15.1 13.8 28.4": ["unappealingly"], "7.0 8.5 3.4": ["atime"], "2.4 19.3 -0.0": ["calumnious"], "0.7 13.0 12.7": ["unisons"], "1.9 19.7 3.3": ["disengenuous"], "18.0 10.0 10.4": ["bannering"], "13.1 31.5 9.2": ["entrenchments"], "8.5 10.6 26.5": ["plumages"], "7.3 16.1 5.9": ["gonig"], "8.7 38.5 8.8": ["murderousness"], "6.5 3.5 31.6": ["gambusia"], "9.0 24.5 10.0": ["coudl"], "2.6 9.6 11.9": ["thoracoscopic"], "14.7 9.3 10.0": ["shlep"], "9.0 13.0 27.6": ["caecilians"], "11.9 7.6 15.4": ["coltsfoot"], "-4.2 1.9 -6.3": ["agented"], "6.9 17.0 4.4": ["misdial"], "10.3 10.6 3.9": ["impertinently"], "23.6 5.4 20.0": ["hatboxes"], "6.0 27.5 4.4": ["perfervid"], "7.7 2.1 2.0": ["cdi"], "5.4 14.8 3.7": ["fetishisation"], "1.9 15.0 -2.3": ["leadings"], "-2.1 5.3 6.7": ["loperamide"], "0.3 5.7 3.8": ["satified"], "-1.8 6.5 13.3": ["meetha"], "6.7 15.8 3.9": ["anathemas"], "10.9 -6.7 -8.8": ["shorlisted"], "18.1 8.3 -3.5": ["rechargable"], "11.8 6.4 18.4": ["baie"], "12.6 20.6 11.6": ["presumedly"], "12.1 8.6 45.1": ["roosterfish"], "1.6 -1.1 -2.7": ["trusteeships"], "-12.5 13.0 9.2": ["contester"], "16.2 -5.8 -1.6": ["maakt"], "-2.2 12.8 5.3": ["inuries"], "18.7 8.4 13.2": ["filamentary"], "4.5 18.6 3.5": ["andhave"], "7.1 -3.3 -4.7": ["autosport"], "-2.0 2.2 3.1": ["eign"], "-2.4 1.7 9.1": ["serger"], "11.0 9.5 11.6": ["fastpaced"], "-0.0 2.5 8.4": ["itinerate"], "6.6 -2.9 5.3": ["resthomes"], "7.2 5.4 40.9": ["sanderlings"], "1.7 5.9 5.8": ["winfs"], "19.5 9.0 29.0": ["conures"], "20.8 4.1 7.2": ["centralisers"], "-3.1 8.4 2.2": ["khatam"], "7.1 9.1 8.7": ["stompboxes"], "13.4 8.6 19.1": ["hoosier"], "-4.4 -3.1 4.2": ["conseil"], "3.8 -1.3 -3.6": ["outsanding"], "14.7 23.6 31.4": ["sapsucker"], "9.0 9.3 11.6": ["beisbol"], "8.1 4.3 15.7": ["canadiens"], "8.6 16.1 17.1": ["alliterations"], "-8.5 6.2 2.6": ["afib"], "0.8 -4.0 5.0": ["caisse"], "7.7 14.7 -4.1": ["detune"], "-6.7 3.6 8.3": ["pseudowires"], "19.5 -5.8 4.4": ["inclues"], "9.9 20.3 36.2": ["shipworms"], "2.8 10.1 11.3": ["yogini"], "3.5 10.6 14.8": ["tweeking"], "-0.7 4.7 2.5": ["borther"], "-1.9 10.2 12.9": ["banishments"], "16.6 21.9 21.8": ["uncurl"], "8.5 6.2 7.5": ["udev"], "16.7 9.9 15.3": ["cockneys"], "2.1 17.7 9.0": ["psycholinguistics"], "2.7 6.3 9.7": ["wordier"], "8.7 9.5 8.6": ["beautful"], "16.3 6.0 20.0": ["stanky"], "0.9 0.2 12.7": ["mayb"], "3.9 21.8 9.6": ["hoofball"], "0.6 10.8 5.6": ["devadasi"], "15.3 12.2 7.2": ["crashlanded"], "2.9 7.5 3.2": ["outsang"], "-1.3 -7.1 -8.0": ["mber"], "4.8 6.1 11.0": ["pptx"], "11.2 19.2 11.8": ["mumbler"], "-2.5 12.4 10.4": ["oneon"], "12.4 23.4 29.7": ["arundo"], "10.3 8.0 5.0": ["isobaric"], "6.7 3.0 5.7": ["dhobis"], "8.5 9.3 7.9": ["ander"], "22.2 10.9 15.0": ["abseils"], "8.2 7.1 10.0": ["mathy"], "1.9 9.7 3.9": ["shaikhs"], "0.8 9.6 4.2": ["inexistence"], "12.1 9.7 4.8": ["ballsiest"], "-16.7 9.1 3.1": ["nontestimonial"], "12.6 16.7 1.0": ["scurrilously"], "7.8 6.0 14.5": ["incising"], "-5.5 5.9 -10.3": ["motived"], "2.2 5.8 5.5": ["elute"], "9.9 13.5 19.5": ["harshing"], "12.3 8.6 23.5": ["toadlets"], "-1.8 -1.5 4.7": ["tice"], "1.3 11.1 17.3": ["handsink"], "3.9 22.0 8.4": ["disinheriting"], "14.4 13.6 10.9": ["gravities"], "-2.8 3.3 7.0": ["voxclever"], "2.2 -4.0 27.7": ["baleage"], "10.3 10.1 5.8": ["continueing"], "16.1 36.5 11.5": ["evilest"], "10.6 12.2 15.9": ["begrudgers"], "11.8 12.0 28.3": ["bellbirds"], "-0.9 1.9 15.9": ["asawa"], "0.5 25.7 7.4": ["consequentialist"], "-2.1 -2.2 4.3": ["perinatology"], "14.4 -6.4 5.3": ["januari"], "-5.3 6.9 13.4": ["invitro"], "20.3 19.7 4.2": ["rumourmongers"], "12.6 14.1 19.4": ["balata"], "2.1 10.1 1.9": ["unmotorable"], "7.2 15.6 5.5": ["anonymising"], "19.8 3.0 40.7": ["beansprouts"], "10.3 14.6 23.1": ["keester"], "21.1 14.1 0.1": ["diplay"], "-0.1 11.3 22.8": ["sunseeds"], "5.7 21.9 10.4": ["biophilia"], "-9.5 12.0 2.4": ["impared"], "-4.1 1.5 -0.5": ["secretariate"], "-1.2 6.0 -0.2": ["idrive"], "-5.7 7.9 3.4": ["supraspinatus"], "-2.5 7.6 7.5": ["endosomal", "vendee"], "0.7 7.8 10.0": ["quadrillionths"], "3.9 10.4 9.6": ["photothermal"], "-0.5 15.2 9.2": ["cohabitated"], "3.4 11.7 1.1": ["dillydally"], "7.1 1.7 8.3": ["whomso"], "13.6 4.5 9.8": ["stiched"], "5.1 10.8 11.8": ["innie"], "17.7 0.8 23.3": ["curlicued"], "1.1 13.8 12.3": ["enum", "subclans"], "14.1 12.2 9.9": ["enervation"], "18.3 13.0 9.0": ["lehman"], "2.2 14.3 44.5": ["ariakensis"], "9.4 1.7 23.0": ["palmoil"], "6.7 3.5 13.0": ["welcomingly"], "10.2 10.6 8.0": ["scribal"], "7.4 14.9 5.6": ["distastefulness"], "-4.8 6.9 7.3": ["saat"], "17.7 12.1 14.6": ["fleeter"], "7.8 4.0 11.0": ["laut"], "7.7 33.5 2.5": ["interlocution"], "9.7 3.3 9.2": ["nanoimprinting"], "-2.1 7.4 10.5": ["nonregulatory"], "-7.0 13.7 10.7": ["reliables"], "1.6 6.8 7.5": ["modlet"], "5.6 7.9 6.7": ["centrehalf"], "6.8 5.4 8.2": ["flocculants"], "7.6 1.7 16.1": ["basketmaker"], "9.3 6.7 35.2": ["viands"], "14.6 7.6 17.4": ["rudraksha"], "-2.4 11.8 6.2": ["mulitiple"], "13.0 3.5 20.2": ["olla"], "0.7 5.8 7.0": ["ried"], "5.3 5.5 -6.0": ["bmcm"], "8.6 11.9 15.3": ["maman"], "16.4 5.8 20.9": ["stairstep"], "15.3 11.5 7.8": ["escalade"], "10.9 7.1 24.2": ["campanula"], "11.1 11.5 6.4": ["disappoinment"], "1.9 5.4 2.3": ["sanitorium"], "9.7 28.0 35.2": ["charr"], "-4.4 16.7 3.6": ["irrespectively"], "7.6 18.0 17.0": ["datums"], "-4.6 15.6 2.0": ["befooled"], "15.7 12.4 23.4": ["minxes"], "-12.3 11.0 -2.3": ["dayanim"], "5.3 11.1 3.3": ["verbalised"], "7.1 1.1 9.6": ["gloveboxes"], "18.2 33.1 19.0": ["warhammer"], "-1.8 10.3 9.4": ["variola"], "-0.6 6.0 11.5": ["asd"], "-3.0 14.8 9.8": ["textualist"], "14.6 13.1 7.8": ["trickledown"], "8.3 11.4 2.8": ["pratical"], "11.5 1.7 17.9": ["pailettes"], "8.6 4.3 -0.5": ["stadiummk"], "-0.3 23.1 4.0": ["masculinist"], "-2.5 15.9 4.4": ["hujra"], "18.7 6.6 17.5": ["untuned"], "9.3 1.0 4.5": ["metrorail"], "5.4 -1.9 10.9": ["perdu"], "5.2 -7.1 10.2": ["fml"], "1.8 6.5 8.6": ["mazda"], "9.6 5.6 20.2": ["beauts"], "2.4 -0.6 8.2": ["tipin"], "8.4 2.7 6.7": ["cuting"], "1.4 4.5 14.9": ["matapos"], "10.4 12.8 5.0": ["undoubtable"], "1.5 5.0 -1.4": ["hightest"], "15.8 -3.4 -9.3": ["partership"], "9.0 5.7 12.5": ["foun"], "1.9 4.0 8.8": ["eing"], "9.2 15.9 29.1": ["bitin"], "4.9 -0.1 9.5": ["agli"], "14.1 10.0 9.0": ["flatteners"], "7.1 9.4 7.0": ["resilence"], "5.4 2.8 33.4": ["tocino"], "5.3 23.3 11.5": ["topologically"], "-9.2 9.2 4.2": ["showup"], "2.0 8.9 11.4": ["rebuildable"], "4.6 13.3 -6.9": ["reenforced"], "-8.7 8.3 -2.8": ["zikir"], "11.6 9.3 9.5": ["stablemasters"], "6.8 26.1 13.1": ["peaceloving"], "14.7 5.8 13.2": ["bankings"], "3.0 10.3 8.7": ["ciliopathies"], "-2.6 6.3 8.8": ["waqt"], "7.4 0.3 12.4": ["rading"], "6.0 14.6 6.3": ["democrates"], "9.5 0.9 -1.2": ["tesa"], "17.6 10.5 16.5": ["squiffy"], "4.0 1.9 7.2": ["custory"], "12.6 7.8 10.2": ["dhoom"], "-0.2 11.5 11.4": ["alienage"], "11.9 20.3 14.5": ["perjorative"], "2.8 10.4 15.0": ["clickin"], "17.4 15.0 21.0": ["trow"], "11.1 6.2 10.4": ["soooooooooo"], "6.4 -3.6 8.5": ["zein"], "3.8 12.1 16.5": ["glas"], "10.1 8.0 -2.3": ["unglamourous"], "10.1 5.6 8.6": ["multiview"], "3.6 10.5 6.0": ["hyperopic"], "14.8 12.7 18.1": ["loofahs"], "7.2 0.1 12.6": ["sydd"], "11.8 3.5 22.0": ["anis"], "3.8 5.5 13.1": ["enfin"], "10.8 5.3 14.6": ["tunage"], "7.4 15.2 4.9": ["volitile"], "-9.1 7.9 1.7": ["cscs"], "16.8 3.5 30.3": ["perogy"], "19.5 11.6 4.0": ["stockowners"], "6.7 11.4 16.2": ["foamers"], "9.3 15.1 7.3": ["retreived"], "17.9 19.9 24.7": ["tribbles"], "7.4 7.2 1.5": ["durning"], "1.4 11.6 7.8": ["orginization"], "3.2 24.4 3.9": ["extraordinariness"], "8.1 11.9 8.8": ["followng"], "8.8 11.2 23.2": ["ecotourist"], "17.8 -7.7 12.5": ["glitzed"], "9.4 18.9 15.3": ["preassigned"], "16.7 13.3 6.3": ["culd"], "10.7 1.3 2.4": ["allowability"], "-1.0 0.4 2.6": ["schoolboard"], "2.7 8.2 13.1": ["inyong"], "0.2 0.8 2.3": ["cted"], "3.0 3.5 3.0": ["halothane"], "5.1 14.4 16.5": ["scholes"], "5.9 13.1 9.5": ["rightaway"], "12.3 7.0 6.1": ["offcourt"], "0.4 18.4 17.7": ["wackjobs"], "-5.5 27.8 8.1": ["counterproductively"], "1.0 5.8 13.0": ["neurite"], "0.4 -2.0 11.3": ["mlk"], "3.2 14.5 12.6": ["pentest"], "7.4 17.9 11.1": ["brod"], "4.4 13.3 10.5": ["disater"], "-2.1 10.3 9.7": ["chemosensitivity"], "18.4 5.6 9.8": ["imagineering"], "13.4 16.7 5.2": ["benchman"], "5.5 4.1 3.1": ["ballkids"], "9.0 7.0 13.1": ["mok"], "7.3 1.8 9.2": ["nome"], "6.0 1.4 7.3": ["calcination"], "1.5 12.1 -0.8": ["appology"], "3.8 -0.4 6.1": ["gynaecomastia"], "12.5 3.4 9.8": ["nickeling"], "22.7 10.4 10.9": ["multibillions"], "8.2 19.1 21.1": ["backslapper"], "11.0 16.0 18.0": ["refasten"], "15.6 8.1 10.4": ["lavatorial"], "6.7 16.9 -0.8": ["evangelic"], "6.6 12.1 14.9": ["aspheres"], "8.7 6.3 14.1": ["middy"], "-1.6 15.7 6.8": ["loggionisti"], "2.4 8.1 5.1": ["orthostatic"], "7.8 4.1 6.6": ["scratchpad"], "-9.9 5.7 8.0": ["mohels"], "11.8 10.7 9.9": ["sheffield"], "-1.6 13.2 9.2": ["tually"], "20.1 4.0 22.3": ["oilskin"], "8.8 7.3 17.8": ["toushin"], "8.8 13.1 9.4": ["pootling"], "9.9 12.5 20.1": ["exected"], "3.2 5.8 13.4": ["sidecut"], "4.5 3.7 1.5": ["signicant"], "8.4 5.0 9.0": ["dios"], "2.8 13.4 8.0": ["jpy"], "15.5 16.3 12.2": ["perforates"], "0.9 16.9 9.5": ["pietistic"], "-1.2 6.0 3.2": ["tolerancing"], "12.0 14.5 3.3": ["uncalibrated"], "10.5 6.4 4.1": ["soho"], "3.7 6.4 15.1": ["gulo"], "-3.1 15.4 10.4": ["subscapularis"], "18.7 31.5 14.3": ["sluggard"], "9.7 29.8 2.6": ["totalitarianisms"], "7.2 12.8 10.5": ["unknot"], "3.6 6.8 10.9": ["kathleen"], "11.6 21.3 36.6": ["butterflying"], "11.1 -3.1 6.0": ["raincover"], "15.5 15.6 25.3": ["dibble"], "22.7 5.5 28.6": ["toastie"], "9.4 6.4 16.4": ["carioca"], "2.6 19.0 0.5": ["atempt"], "15.5 36.2 13.2": ["supersoldier"], "9.3 4.2 9.5": ["hepped"], "1.2 -2.7 5.6": ["bahk"], "17.4 10.6 10.1": ["mediasphere"], "9.6 11.8 8.9": ["toey"], "0.5 9.1 7.1": ["clodronate"], "-1.4 12.1 8.0": ["nallahs"], "7.6 3.7 19.8": ["lysate"], "-4.4 1.9 11.2": ["thoracolumbar"], "17.4 5.5 30.0": ["sifaka"], "13.2 17.2 5.5": ["thathave"], "16.9 4.1 18.7": ["senoritas"], "4.9 10.8 13.8": ["drudged"], "21.6 10.0 13.0": ["nanosize"], "13.8 3.4 19.3": ["cupcakery"], "1.5 10.5 3.9": ["ringcraft"], "-0.2 -1.4 4.0": ["overexpenditure"], "20.5 16.3 16.7": ["baldest"], "9.8 10.2 5.5": ["ixnay"], "10.0 16.6 11.9": ["plutonic"], "6.2 -13.6 4.0": ["directo"], "10.2 21.9 6.0": ["rightbloggers"], "12.4 9.4 9.6": ["buldings"], "9.8 12.3 8.5": ["flexibile"], "1.3 2.8 3.5": ["soigneurs"], "12.9 -3.5 4.8": ["qaurter"], "1.3 5.1 -4.9": ["elos"], "3.9 0.2 12.6": ["feliz"], "-6.3 17.6 8.5": ["aurat"], "10.7 28.7 6.5": ["malediction"], "1.5 22.6 14.4": ["immoderately"], "-4.7 6.1 11.1": ["cathepsin"], "15.8 1.8 33.1": ["fishier"], "4.7 0.4 13.2": ["windshirt"], "-1.9 2.4 2.4": ["neuroethics"], "-2.4 7.9 4.5": ["cobicistat"], "-6.6 8.1 11.3": ["coxie"], "7.4 5.3 23.5": ["grasscutter"], "1.4 5.2 18.1": ["beader"], "22.3 13.0 12.0": ["scallies"], "7.5 15.9 0.9": ["inyanga"], "9.0 14.3 4.9": ["powe"], "1.1 -0.4 9.8": ["finearts"], "5.3 27.3 15.1": ["disenchant"], "1.4 -3.2 15.6": ["henley"], "-0.6 3.6 15.6": ["diye"], "16.9 1.9 16.9": ["funkster"], "0.9 6.9 9.0": ["multidrug"], "22.3 10.4 18.1": ["snaffles"], "9.6 13.0 23.8": ["salinated"], "4.0 13.7 9.6": ["nerveracking"], "5.2 7.3 17.4": ["katy"], "-2.6 8.5 0.8": ["umar"], "16.5 -0.4 23.1": ["blackwood"], "7.6 14.3 9.0": ["tohis"], "4.1 7.5 11.1": ["soundbars"], "-1.8 5.4 1.6": ["transman"], "3.1 6.4 12.1": ["xc"], "11.3 14.9 8.9": ["scintillate"], "12.6 10.0 11.5": ["fuzziest"], "12.3 5.6 3.4": ["apalooza"], "-6.1 2.2 14.4": ["nonpersonnel"], "1.6 -0.4 9.0": ["eurodollars"], "16.2 13.6 8.7": ["mmorpg"], "5.2 15.3 10.3": ["nonfactors"], "12.1 9.3 21.3": ["foodstocks"], "15.7 3.5 7.3": ["descarga"], "-0.5 10.6 15.9": ["gett"], "2.8 6.4 -0.6": ["jn"], "3.5 15.8 14.9": ["anciently"], "4.1 6.0 5.5": ["ubiquinone"], "-0.2 3.9 3.6": ["cannabinor"], "8.7 12.6 16.2": ["glottal"], "2.7 3.4 11.4": ["feebates"], "-4.2 10.7 11.1": ["twon"], "-1.2 11.1 18.2": ["tanan"], "9.6 -1.0 -1.2": ["telemanagement"], "24.4 2.8 5.3": ["qtrly"], "-1.3 7.4 12.7": ["lysates"], "11.9 0.3 18.9": ["chocker"], "20.4 11.4 -4.8": ["ebookstore"], "22.3 16.3 27.2": ["fishlike"], "4.8 24.4 10.2": ["willfull"], "5.1 4.2 8.8": ["recontouring"], "1.5 14.2 1.3": ["unscrutinized"], "15.7 21.5 3.9": ["celebritydom"], "13.1 25.0 10.8": ["repugs"], "-4.4 7.7 13.5": ["gustong"], "12.3 13.4 5.2": ["nonintegrated"], "4.5 6.9 7.5": ["dilettantish"], "10.2 -3.8 3.5": ["architectual"], "9.4 10.1 15.6": ["polyploid"], "9.6 7.9 18.6": ["tsubo"], "-0.1 3.7 11.0": ["ureteroscopy"], "22.7 4.4 20.8": ["dudette"], "9.4 7.3 14.8": ["motorscooter"], "2.7 10.3 9.8": ["lthe"], "5.0 8.9 12.2": ["addr"], "12.5 13.9 5.0": ["farreaching"], "16.7 37.9 20.9": ["necromorph"], "-6.7 10.2 5.8": ["unschoolers"], "-1.5 -4.7 4.2": ["vaginoplasty"], "2.3 5.4 13.4": ["scool"], "16.8 -0.1 6.4": ["topia"], "4.4 18.0 14.4": ["oldman"], "5.1 -14.4 10.0": ["threeand"], "-10.5 -1.5 1.9": ["mentalhealth"], "12.0 -6.3 -3.3": ["developmen"], "-2.2 4.8 6.7": ["salutatory"], "9.6 7.1 4.9": ["nanomotors"], "-1.6 13.2 5.9": ["hereinabove"], "12.5 8.7 4.2": ["watercooled"], "4.0 9.3 12.0": ["vuggy"], "10.3 8.9 3.2": ["befogged"], "-1.0 16.4 10.4": ["schemata"], "5.0 15.2 8.0": ["calmy"], "1.4 5.5 7.3": ["thal"], "15.7 10.9 37.1": ["mulligatawny"], "0.5 9.8 13.6": ["minim"], "1.0 0.6 7.9": ["intergovernment"], "12.7 11.0 13.6": ["seafronts"], "12.0 4.5 4.9": ["rubgy"], "9.3 13.9 9.9": ["sharrow"], "12.4 9.1 11.0": ["hardearned"], "-2.0 7.3 9.0": ["ziconotide"], "20.3 8.3 8.0": ["tsarina"], "2.4 4.7 5.1": ["sored"], "-1.8 8.4 -5.5": ["charg"], "10.2 15.1 -4.5": ["copiloted"], "2.6 16.1 6.9": ["cefixime"], "-2.0 14.9 1.5": ["uncredentialed"], "-5.5 4.1 0.9": ["whichare"], "8.7 7.2 4.1": ["ultrasonically"], "4.3 12.5 -2.5": ["disassociates"], "7.6 1.8 7.2": ["produits"], "4.3 11.7 11.1": ["aroudn"], "19.9 22.0 15.0": ["tenpins"], "-1.5 -1.6 23.4": ["barleys"], "-15.7 5.1 3.1": ["methimazole"], "16.1 26.5 7.4": ["deafens"], "-5.6 0.3 7.3": ["otosclerosis"], "0.7 5.4 7.1": ["somos"], "25.5 14.5 7.4": ["wizardy"], "5.5 5.5 6.2": ["creakier"], "5.2 3.9 4.2": ["ngs"], "5.7 8.0 -9.3": ["recategorized"], "9.5 8.0 0.3": ["wherethe"], "18.9 24.0 3.9": ["juggernaught"], "24.1 20.0 15.6": ["cyclopean"], "8.0 12.7 11.8": ["goras"], "6.9 21.1 6.3": ["fusilier"], "9.5 18.1 38.9": ["dunlins"], "4.6 28.3 5.9": ["littleness"], "3.9 12.1 16.3": ["countercurrent"], "-2.4 13.7 7.5": ["diwas"], "11.3 9.0 12.4": ["dumba"], "14.5 14.0 26.8": ["encrustations"], "-0.1 9.7 3.2": ["helmsmanship"], "7.0 12.7 15.2": ["stachybotrys"], "4.2 2.3 10.6": ["flavonol"], "-1.4 1.5 3.9": ["yojana"], "-2.1 2.5 10.7": ["lambdas"], "8.6 6.6 19.8": ["lampworking"], "11.1 22.8 5.3": ["shaikh"], "3.3 19.4 -2.4": ["monism"], "0.3 11.5 10.8": ["synapsis"], "7.1 -4.4 4.1": ["daytimer"], "3.4 7.0 14.0": ["consy"], "7.9 5.0 32.1": ["albondigas"], "-3.9 20.9 6.2": ["trama"], "12.8 25.8 10.5": ["unsee"], "0.3 11.9 7.8": ["prayerbook"], "-1.1 9.4 7.0": ["stageplay"], "0.2 1.5 4.3": ["woolgrower"], "-0.6 11.1 6.7": ["beide"], "14.1 6.4 17.7": ["overinvest"], "16.9 10.0 8.4": ["burgandy"], "7.8 13.7 14.4": ["reproducers"], "-0.5 16.1 13.8": ["koka"], "13.7 9.9 20.6": ["carboy"], "4.1 4.4 -9.6": ["oximeters"], "10.2 8.2 7.2": ["woz"], "23.1 14.9 13.9": ["chiselers"], "6.6 2.1 11.9": ["laner"], "-5.8 6.3 6.2": ["amand"], "14.1 15.2 24.0": ["mynahs"], "-2.0 5.8 13.1": ["jaana"], "13.4 20.7 12.3": ["venemous"], "5.7 3.8 12.9": ["chaconne"], "9.1 7.1 6.8": ["decrescendo"], "-5.4 1.3 3.2": ["counterfoils"], "6.0 6.3 5.0": ["fiving"], "2.7 9.2 3.3": ["overreported"], "9.2 16.4 10.0": ["floormates"], "8.0 1.5 10.2": ["polylactide"], "-4.8 3.1 10.5": ["flowthrough"], "-4.6 7.8 -1.6": ["storywriter"], "4.9 6.5 -5.1": ["videochat"], "3.8 3.1 5.5": ["neuromas"], "11.0 0.3 20.5": ["moc"], "11.3 1.3 15.4": ["karakul"], "11.0 7.7 25.4": ["kir"], "21.2 20.8 24.8": ["dracula"], "7.2 22.7 0.9": ["administraton"], "9.3 22.3 17.3": ["vampiress"], "6.4 4.3 -2.5": ["mobisite"], "-3.5 6.4 -2.3": ["notonly"], "-5.1 -2.4 2.1": ["physicans"], "11.7 8.7 16.5": ["oxyacetylene"], "5.3 12.5 6.7": ["dialtone"], "14.6 20.2 9.2": ["interwebz"], "11.3 -2.5 12.8": ["sity"], "4.3 2.9 17.1": ["springtimes"], "9.6 16.2 18.1": ["kneelift"], "6.6 3.3 8.2": ["jeder"], "15.8 5.8 22.6": ["couverture"], "1.1 29.0 5.1": ["supercruise"], "6.4 1.0 12.5": ["betw"], "12.1 13.9 14.7": ["hayshed"], "7.4 -2.3 15.3": ["classique"], "-1.1 4.6 11.7": ["abby"], "18.2 1.2 19.6": ["kidlets"], "9.1 8.8 8.4": ["finishline"], "9.2 17.2 2.2": ["antitoxins"], "4.9 -1.5 17.2": ["liquour"], "5.7 -3.7 8.7": ["solderable"], "14.5 2.4 14.2": ["superdome"], "7.5 6.2 13.0": ["dabbawala"], "6.7 15.4 7.6": ["egoistical"], "-2.9 3.2 7.9": ["vidwan"], "-8.1 9.7 -0.8": ["asylee"], "-1.6 11.0 7.7": ["maam"], "7.2 -0.1 16.6": ["quaddie"], "1.7 21.6 5.1": ["outrush"], "3.0 24.0 5.4": ["volubility"], "10.3 7.7 5.5": ["tranformed"], "0.3 11.6 11.6": ["jahan"], "-4.7 -0.7 13.9": ["territorywide"], "7.1 12.1 9.8": ["quavered"], "4.5 7.0 6.5": ["hydrogens"], "-1.7 19.2 8.0": ["greiving"], "13.0 18.0 10.2": ["queuers"], "4.5 16.3 7.1": ["fortissimos"], "17.0 8.1 26.2": ["paloma"], "7.7 12.2 1.4": ["pointsmen"], "9.2 28.1 19.9": ["mondegreen"], "-1.3 8.0 4.6": ["amit"], "8.4 25.1 12.0": ["coarsens"], "2.4 13.5 1.2": ["nontheistic"], "3.5 1.0 2.7": ["nonequity"], "11.4 6.5 21.5": ["gamblin"], "-1.0 6.0 16.6": ["supercentenarian"], "6.5 3.4 12.9": ["pyritized"], "2.8 15.8 3.5": ["bhoomi"], "2.7 5.5 4.9": ["underbalanced"], "11.0 6.5 20.0": ["calfs"], "16.0 11.2 16.6": ["bubblehead"], "-0.4 15.0 9.5": ["recross"], "-1.5 1.6 3.5": ["aquittal"], "-2.6 5.2 10.2": ["defluxing"], "23.8 6.9 19.1": ["steelmills"], "0.9 2.7 12.9": ["macrodiamonds"], "17.7 18.5 25.0": ["jouster"], "3.4 9.7 3.6": ["parites"], "6.0 3.2 16.5": ["mya"], "6.2 8.2 4.3": ["cryptex"], "5.7 -7.7 -10.5": ["emplyees"], "13.2 9.6 1.1": ["machers"], "-0.4 21.2 23.6": ["shotshell"], "-3.4 19.5 10.0": ["nonactive"], "3.6 15.0 5.7": ["concealments"], "6.8 13.7 7.9": ["motorcaded"], "12.4 25.2 8.7": ["blackguards"], "4.5 16.0 3.2": ["droppable"], "1.8 8.4 5.9": ["ivan"], "7.4 12.9 9.5": ["instantiating"], "10.8 11.3 9.1": ["raths"], "8.9 10.3 6.8": ["healtcare"], "11.2 -5.8 -1.1": ["caroled"], "3.9 3.4 8.8": ["tual"], "0.6 -5.0 13.6": ["anadditional"], "14.4 7.8 20.4": ["truckful"], "0.1 3.3 8.4": ["netcast"], "7.8 5.5 14.3": ["frances"], "1.2 3.5 12.8": ["fibrillar"], "15.3 7.2 17.6": ["handsewn"], "-6.5 9.8 -1.9": ["erythropoietic"], "23.8 6.5 21.4": ["pulper"], "8.8 22.3 14.8": ["votebanks"], "3.9 -0.9 10.8": ["studmaster"], "21.5 18.2 16.5": ["tightwire"], "3.9 -0.5 12.8": ["rehears"], "9.8 2.9 8.7": ["multiteam"], "-1.3 12.6 -0.1": ["recordist"], "5.6 5.9 -2.7": ["videomaker"], "-0.0 0.7 14.7": ["gimmer"], "-7.0 9.2 0.7": ["cytopenias"], "-5.7 4.1 7.6": ["psychophysiological"], "14.6 1.9 34.2": ["boeuf"], "14.7 4.5 29.0": ["morcilla"], "2.8 3.6 8.3": ["livres"], "2.9 3.7 0.8": ["noradrenalin"], "12.7 35.1 8.3": ["stealthiness"], "0.4 13.1 21.4": ["ooking"], "3.3 6.1 -2.2": ["direkt"], "-4.7 15.7 11.2": ["emegency"], "8.2 2.5 11.6": ["nondomestic"], "15.0 -2.1 16.5": ["cornrow"], "19.3 16.7 20.6": ["edgeless"], "8.4 2.0 8.7": ["metalliferous"], "15.8 27.5 8.2": ["bourgeoisies"], "16.7 36.2 16.1": ["shurikens"], "13.3 12.4 16.2": ["necro"], "21.3 6.5 29.5": ["nubbly"], "16.6 3.0 -1.9": ["trailblazed"], "21.9 10.5 9.1": ["wheatfields"], "-8.5 4.5 1.5": ["reprogrammability"], "-1.4 10.3 -3.3": ["noteriety"], "0.0 9.5 5.4": ["beltpack"], "-4.2 14.2 6.2": ["coordinations"], "4.8 9.7 19.7": ["tuan"], "-0.9 26.7 2.5": ["stauncher"], "2.7 16.0 6.7": ["stroy"], "-1.3 3.4 -4.3": ["thereport"], "-0.7 29.8 7.1": ["dogmatist"], "0.4 8.6 7.4": ["underrepresent"], "10.8 5.6 6.1": ["slideware"], "10.2 3.3 -0.0": ["estadounidense"], "19.6 15.4 1.7": ["accidentially"], "7.1 17.3 7.5": ["kosovo"], "11.4 2.9 28.5": ["cendol"], "-1.0 8.2 14.4": ["becaues"], "-0.9 14.2 0.9": ["unforseeable"], "22.4 6.2 15.8": ["malus"], "12.5 12.6 3.2": ["wringers"], "16.5 12.6 11.9": ["skivers"], "-4.9 6.1 -0.6": ["nontraffic"], "6.7 13.0 9.6": ["mobikes"], "9.3 7.3 11.1": ["anticlines"], "10.3 12.5 10.6": ["shizzlr"], "14.1 9.5 13.4": ["bernard"], "8.0 17.7 10.3": ["monomaniac"], "19.8 6.6 28.1": ["eskimos"], "12.4 5.7 10.6": ["boops"], "12.2 5.3 34.8": ["gochujang"], "11.3 -10.3 2.3": ["thermoformer"], "12.4 8.8 14.3": ["trilbies"], "6.7 -4.8 1.8": ["newslinks"], "13.8 20.1 8.1": ["bootprints"], "9.2 13.3 10.1": ["laundryman"], "9.5 -3.2 4.2": ["easyfinancial"], "-1.8 12.2 11.2": ["metrologists"], "15.9 16.5 24.4": ["mayapple"], "5.0 -0.9 3.6": ["pratices"], "-3.2 10.7 14.1": ["lalaki"], "9.3 7.9 15.1": ["unhygenic"], "9.5 4.0 5.3": ["alfred"], "10.8 12.2 5.6": ["flagellar"], "9.1 27.9 11.9": ["treelines"], "-2.4 -2.2 11.0": ["housewalk"], "5.5 4.6 37.9": ["cannellini"], "16.2 25.8 10.5": ["peskiest"], "12.2 1.1 7.7": ["fitouts"], "1.8 19.9 7.6": ["racialization"], "-0.1 7.7 2.4": ["knowledgebases"], "17.7 11.6 27.4": ["cutt"], "7.6 8.8 17.6": ["deben"], "-1.7 9.6 5.9": ["ridealong"], "19.3 21.3 7.8": ["modernday"], "8.8 16.3 1.6": ["immolations"], "13.2 5.6 11.7": ["calligraphies"], "3.2 -5.2 6.4": ["fractionates"], "7.0 7.3 21.4": ["sleighing"], "12.9 -4.6 -3.2": ["solubilized"], "18.5 6.2 38.2": ["musubi"], "20.2 3.8 14.2": ["supercold"], "16.1 14.5 17.6": ["japery"], "6.5 10.9 3.7": ["diaristic"], "3.9 6.9 11.2": ["nalas"], "3.9 9.8 5.7": ["notto"], "6.6 23.3 12.6": ["recolonizing"], "14.6 6.0 18.7": ["cheongsams"], "9.1 12.8 3.5": ["blazars"], "-1.6 11.6 7.3": ["partymate"], "-3.7 16.1 7.5": ["confliction"], "4.1 6.8 3.3": ["championsip"], "7.0 13.7 14.1": ["wideopen"], "8.5 12.8 12.3": ["viewports"], "8.5 6.5 -2.1": ["reflash"], "6.1 -0.3 1.3": ["fase"], "9.9 6.3 29.9": ["pakodas"], "13.5 12.4 5.4": ["celebutard"], "8.4 6.4 10.9": ["watermills"], "-5.1 14.4 -3.5": ["dominionist"], "-0.3 10.6 13.7": ["clockspeeds"], "0.1 8.6 20.1": ["wazwan"], "14.7 7.9 44.1": ["arowana"], "9.2 10.0 7.0": ["supermiddleweight"], "-3.8 26.9 9.8": ["conjunctural"], "4.5 9.6 9.1": ["possie"], "0.4 -0.6 -1.7": ["contrib"], "6.2 17.2 11.0": ["mainliners"], "5.1 30.3 15.5": ["liveth"], "-0.5 8.0 4.6": ["bonified"], "0.1 18.6 0.6": ["describer"], "11.7 11.4 11.0": ["unrung"], "3.9 10.6 3.0": ["sneakernet"], "7.7 5.4 15.5": ["bubbies"], "9.1 10.4 16.6": ["circovirus"], "5.5 7.6 0.9": ["upfitted"], "4.2 7.0 0.7": ["agen"], "14.1 -4.9 4.1": ["comapany"], "13.2 9.4 30.5": ["leger"], "2.2 4.8 14.3": ["rolldown"], "7.3 -0.2 20.8": ["studenty"], "3.4 19.2 14.2": ["adlibbing"], "8.0 13.9 9.7": ["neighouring"], "23.8 17.5 22.1": ["loup"], "-1.1 14.8 1.1": ["odiousness"], "2.9 13.8 4.1": ["fatique"], "8.3 0.6 4.3": ["nasair"], "0.4 2.9 11.5": ["superstreet"], "4.9 -1.7 12.9": ["italiana"], "9.0 13.8 17.4": ["hehehehe"], "4.0 7.8 3.9": ["derecognising"], "7.8 -10.8 -4.8": ["willprovide"], "17.5 13.4 12.1": ["circumstellar"], "4.5 4.4 14.8": ["monensin"], "5.4 16.6 20.5": ["lepto"], "-3.5 7.9 6.6": ["sarpanchas"], "6.3 10.9 14.4": ["enterocytes"], "18.1 -1.9 -1.9": ["frrom"], "19.5 -1.6 3.9": ["empresa"], "-0.7 1.4 6.2": ["nominess"], "14.2 19.2 11.8": ["policia"], "2.9 3.9 4.1": ["initated"], "11.4 17.1 8.2": ["poofters"], "21.7 19.8 19.9": ["nethers"], "11.5 20.8 35.1": ["chafer"], "6.3 6.5 10.4": ["geeksugar"], "12.3 13.1 11.2": ["exhaustedly"], "10.2 4.4 33.1": ["whimbrel"], "-1.1 10.8 4.5": ["feeback"], "1.7 27.0 6.3": ["extirpating"], "4.3 8.5 16.7": ["armstrong"], "4.5 13.6 4.5": ["jacketless"], "-0.5 -3.0 0.6": ["respresentatives"], "2.9 12.1 18.8": ["oneg"], "-5.0 5.2 -7.1": ["representating"], "6.4 10.9 10.2": ["komatiite"], "17.1 5.4 20.0": ["epoxied"], "3.7 4.3 9.4": ["pel"], "1.0 1.2 11.5": ["kamancheh"], "-4.8 11.5 5.9": ["decommits"], "10.1 4.9 16.6": ["lustier"], "5.4 14.2 10.8": ["ephrin"], "4.7 2.3 17.1": ["muk"], "15.2 5.5 44.4": ["lugworms"], "18.6 5.1 23.7": ["jardiniere"], "1.8 11.2 14.3": ["sehri"], "13.0 8.0 13.8": ["bleb"], "10.9 -3.1 6.0": ["moritorium"], "12.2 12.3 6.2": ["wirelines"], "20.1 3.2 7.0": ["highdefinition"], "5.1 6.1 6.3": ["triode"], "11.7 10.9 15.3": ["sandpapered"], "4.7 21.0 9.7": ["truthy"], "9.9 12.5 15.8": ["microfractures"], "1.6 5.0 0.3": ["garnisheeing"], "15.8 10.7 38.8": ["honu"], "4.4 -1.3 12.7": ["hefyd"], "12.2 24.0 10.0": ["communitarians"], "9.2 -3.6 5.8": ["soa"], "4.1 6.1 18.2": ["elliot"], "12.5 10.1 4.3": ["rebuying"], "8.0 15.7 15.5": ["fencelines"], "17.4 20.2 13.4": ["abid"], "11.0 3.5 1.7": ["acccess"], "11.2 -6.5 8.6": ["indice"], "3.1 20.2 7.8": ["pithiness"], "13.5 13.2 15.3": ["peoplewho"], "14.6 -3.6 17.7": ["babydolls"], "7.6 6.1 19.7": ["bucker"], "2.6 4.3 19.5": ["resuspended"], "5.0 7.7 0.3": ["infoshop"], "8.3 -3.1 2.8": ["mbs"], "17.1 -0.7 15.5": ["drays"], "3.2 13.8 9.7": ["majorless"], "16.8 14.4 18.5": ["grislier"], "6.3 11.2 11.7": ["waspishly"], "16.6 18.5 14.4": ["bluey"], "9.4 6.9 -5.0": ["postered"], "14.6 4.6 26.6": ["flambeed"], "-2.8 -1.5 6.5": ["thecounter"], "11.6 9.5 7.2": ["portait"], "12.5 19.5 15.9": ["squibbing"], "2.4 11.1 0.8": ["ruction"], "1.3 -9.4 9.9": ["nonsubsidized"], "6.2 0.0 5.4": ["racebooks"], "2.0 5.1 16.7": ["annua"], "4.4 14.7 8.8": ["modulatory"], "-1.6 10.1 5.5": ["ramos"], "13.7 10.0 10.6": ["trollops"], "19.5 -3.4 7.5": ["smackeroos"], "8.8 23.0 6.0": ["mudslingers"], "9.3 3.7 8.6": ["jotter"], "1.3 6.5 18.8": ["gila"], "11.4 7.2 23.8": ["cnidarians"], "12.5 15.2 13.3": ["lingerers"], "19.0 2.1 7.7": ["overexpanded"], "8.6 19.6 15.6": ["lydia"], "-0.3 5.8 12.6": ["lett"], "17.4 16.3 13.1": ["keelhauled"], "4.3 1.1 8.7": ["tafluprost"], "7.6 9.2 20.4": ["ultracet"], "9.6 7.3 10.7": ["fbc"], "13.0 -6.7 3.4": ["millin"], "3.0 9.4 6.4": ["neotame"], "4.6 20.2 14.5": ["scarry"], "23.0 5.0 15.3": ["barefeet"], "9.2 6.5 5.2": ["upheavel"], "-0.4 25.5 7.6": ["unsub"], "1.9 1.9 4.0": ["odo"], "11.1 19.9 10.0": ["semidarkness"], "13.3 10.8 12.4": ["crammers"], "4.2 16.0 4.3": ["vulnerabilites"], "-8.8 5.3 3.8": ["bivariate"], "1.9 16.8 10.3": ["archaism"], "10.2 9.4 12.5": ["fantastico"], "8.0 5.7 6.4": ["motivic"], "1.8 15.5 -2.1": ["simlar"], "6.6 -5.1 0.8": ["deliverd"], "5.5 -5.8 7.5": ["pree"], "14.3 12.6 8.6": ["poohbahs"], "-2.9 14.2 6.8": ["dayan"], "6.3 29.4 7.4": ["perpetuator"], "-0.3 3.5 12.8": ["magagawa"], "-0.0 25.7 14.6": ["biotypes"], "-2.2 12.2 4.4": ["underseen"], "15.1 12.4 15.1": ["weatherboards"], "6.7 5.1 13.6": ["claro"], "16.1 6.2 20.6": ["marcasite"], "-0.3 2.3 12.6": ["crampy"], "11.3 14.1 5.3": ["sappiest"], "-0.4 15.4 11.9": ["ruchika"], "-1.4 14.3 11.5": ["overshifted"], "9.7 -3.8 31.5": ["sopa"], "4.6 24.5 13.0": ["fruitlessness"], "8.3 6.0 27.8": ["mayonaise"], "-3.3 15.2 2.4": ["callsigns"], "6.5 0.4 18.8": ["cheo"], "10.5 4.6 11.6": ["handiworks"], "19.8 5.5 15.9": ["haemorrhoid"], "4.2 17.9 10.4": ["bookishness"], "6.5 12.7 13.6": ["ferroelectricity"], "1.0 2.7 2.5": ["expectd"], "-0.1 2.0 -4.1": ["pyschologist"], "16.0 2.0 9.8": ["tootled"], "5.0 19.0 7.2": ["moodiest"], "16.3 11.0 25.8": ["refugium"], "7.5 21.1 11.7": ["surcease"], "3.1 13.3 9.7": ["wecan"], "19.7 18.4 10.1": ["avalanching"], "8.3 7.1 8.9": ["wailers"], "8.2 17.4 -3.3": ["psychokinesis"], "1.8 -0.3 14.2": ["ffoulkes"], "1.2 -2.6 1.9": ["incubatees"], "3.4 4.7 18.8": ["bluebook"], "10.7 9.9 5.1": ["photocatalysts"], "-1.4 3.5 7.7": ["avodart"], "8.4 10.0 1.2": ["vigilanteism"], "2.0 8.0 19.2": ["usko"], "6.0 8.4 9.3": ["silicide"], "10.0 11.5 20.3": ["cowman"], "15.4 10.0 -0.6": ["electonic"], "4.1 7.4 7.0": ["optima"], "1.7 11.0 5.4": ["helpfull"], "11.4 9.2 4.7": ["unvalued"], "18.3 11.3 20.3": ["erratics"], "11.0 15.2 26.2": ["cyclamens"], "12.9 20.2 18.3": ["desultorily", "ewwwww"], "1.9 12.2 3.4": ["theinformation"], "4.1 4.9 10.8": ["sarcomere"], "11.0 8.8 7.3": ["moniter"], "9.8 11.7 10.4": ["inflexibilities"], "-4.8 -0.7 4.9": ["asha"], "21.5 1.7 4.8": ["asmall"], "9.8 11.5 6.8": ["myoelectric", "unexpectantly"], "10.1 12.8 10.8": ["herniate"], "13.3 28.5 4.0": ["odiously"], "6.6 1.9 9.0": ["gayageum"], "-0.8 12.3 21.5": ["fodders"], "7.7 10.2 19.2": ["offbreaks"], "10.9 12.0 21.7": ["lores"], "12.5 25.8 7.8": ["guvmint"], "5.8 12.9 21.6": ["planchet"], "-1.4 4.9 16.9": ["malas"], "9.9 19.4 14.6": ["mesmerism"], "-3.7 10.1 -3.5": ["aicc"], "5.2 12.8 18.2": ["rudy"], "-0.1 5.7 1.1": ["profesor"], "13.5 6.7 11.7": ["subretinal"], "12.8 13.5 10.9": ["cosiest"], "14.2 18.2 11.4": ["rammer"], "14.7 18.0 11.0": ["sheeplike"], "12.2 -1.1 26.3": ["sendings"], "-7.1 12.3 1.5": ["truthout"], "-2.4 11.6 2.6": ["frontburner"], "4.3 9.3 -5.9": ["negociations"], "-5.5 11.2 5.2": ["probating"], "5.0 12.9 11.1": ["inebriating"], "14.1 4.3 7.1": ["stemcells"], "7.0 33.9 4.6": ["enormities"], "2.5 15.6 3.2": ["challenege"], "10.0 18.2 15.5": ["indistinguishably"], "10.6 10.8 -3.8": ["recents"], "5.0 5.7 2.1": ["compaines"], "14.8 14.5 6.6": ["splatterfest"], "-1.8 1.0 13.0": ["pigmentary"], "0.7 15.8 4.3": ["proselyte"], "17.2 3.8 9.3": ["stiffy"], "-0.6 18.0 4.7": ["celibates"], "7.1 10.8 3.6": ["heatmap"], "-6.4 5.4 2.2": ["anorectal"], "-5.1 1.0 1.3": ["nmol"], "6.9 1.9 20.0": ["priss"], "5.8 9.9 2.9": ["lution"], "10.2 5.3 27.0": ["craisins"], "5.4 -11.2 -2.5": ["threeyears"], "7.7 8.7 23.5": ["barefooting"], "-5.9 6.6 11.3": ["anu"], "14.1 19.1 22.9": ["boofheads"], "7.0 14.7 2.9": ["useof"], "13.3 24.2 7.8": ["sicarios"], "13.0 31.1 3.6": ["myrmidons"], "2.1 4.6 12.0": ["satu"], "9.6 15.0 14.6": ["slingy"], "24.8 11.7 22.7": ["yoyos"], "9.1 3.1 11.5": ["etsy"], "24.0 10.7 15.0": ["teenie"], "4.0 5.9 12.7": ["lithogeochemical"], "11.4 14.4 8.8": ["flashily"], "3.1 1.9 4.9": ["consultee"], "6.1 22.5 15.6": ["tradeskill"], "8.2 4.4 -2.9": ["epigraphy"], "5.5 9.1 22.4": ["graupel"], "12.7 21.2 9.9": ["draconic"], "3.4 13.1 -3.6": ["teratogen"], "7.3 14.4 7.8": ["thumbsucking"], "-1.1 6.4 8.1": ["terlipressin"], "19.6 22.8 9.5": ["powerlessly"], "19.6 11.1 21.2": ["sponsons"], "15.9 14.7 14.5": ["doorsill"], "4.3 -0.9 -5.1": ["morren"], "3.1 16.8 5.8": ["deboard"], "-2.7 8.2 11.4": ["coulds"], "18.2 -6.0 3.1": ["thismonth"], "4.8 7.6 7.7": ["hoho"], "6.7 6.4 12.5": ["jackpotted", "patelankur"], "-2.4 5.7 12.4": ["choreo"], "11.1 9.7 7.1": ["takeing"], "5.6 -3.2 4.8": ["mayer"], "21.8 20.1 12.8": ["pocking"], "3.5 16.9 6.9": ["crediblity"], "10.6 5.1 -0.3": ["topliners"], "7.8 17.8 7.7": ["flashguns"], "20.9 0.4 14.0": ["wallscapes"], "-3.3 2.5 9.1": ["leadtime"], "21.6 12.6 11.3": ["endoskeleton"], "6.3 9.3 5.3": ["geofences"], "3.7 7.8 15.7": ["lohan"], "5.7 -2.4 3.8": ["biosurgical"], "0.2 2.3 7.6": ["wara"], "10.5 11.1 4.4": ["hungary"], "-2.8 0.1 6.5": ["sasy"], "0.6 10.2 10.8": ["coreholes"], "11.4 3.0 -2.4": ["accordant"], "18.1 5.7 16.3": ["recontoured"], "13.7 27.2 19.2": ["tailhook"], "9.4 13.2 5.8": ["panoptic"], "19.0 7.3 20.3": ["hayrack"], "15.0 10.0 12.3": ["haken"], "-2.4 0.6 11.2": ["rotarians"], "8.8 6.6 7.1": ["glasgow"], "12.8 -3.6 8.1": ["slummed"], "6.1 10.9 4.6": ["stlye"], "-3.2 18.1 16.8": ["outcrossing"], "4.8 12.3 24.8": ["jasmines"], "5.8 9.0 10.5": ["unpunctuated"], "0.4 8.4 15.5": ["dyking"], "9.2 14.3 4.1": ["brillance"], "-7.7 4.2 0.5": ["sectary"], "0.2 14.6 0.2": ["mahalla"], "4.7 12.5 49.1": ["miniseason"], "1.9 -0.5 1.8": ["addd"], "8.0 -4.0 6.0": ["playwear"], "5.6 1.6 17.6": ["chaplet"], "11.3 0.7 1.2": ["bekend"], "4.6 9.0 12.1": ["disagreeably"], "15.8 8.2 9.2": ["prominences"], "3.5 -0.1 11.6": ["lleol"], "1.2 5.7 4.3": ["biotransformation"], "12.2 19.1 10.9": ["magnetopause"], "12.6 8.0 12.2": ["calendering"], "18.4 9.4 33.7": ["spanikopita"], "-8.0 21.4 5.5": ["repitition"], "6.2 8.3 6.8": ["ingratiatingly"], "10.2 7.6 9.9": ["ashing"], "5.6 -3.3 5.4": ["butanediol"], "16.3 10.5 11.4": ["nonconductive"], "10.6 17.6 16.2": ["gomen"], "4.6 2.3 13.5": ["walton"], "-0.0 7.2 4.5": ["sulindac"], "12.5 4.5 28.7": ["wheaty"], "14.9 2.6 7.5": ["magnetoencephalography"], "6.7 2.5 13.4": ["wearings"], "19.0 21.1 13.5": ["joypads"], "21.7 6.3 22.0": ["giganteus"], "1.0 20.7 0.9": ["andersoncooper"], "13.3 2.7 30.4": ["birchbark"], "10.9 -5.3 8.3": ["profi"], "0.3 -3.7 1.4": ["whih"], "4.4 1.0 3.4": ["transurethral"], "3.0 10.9 12.8": ["motorcylce"], "-8.3 19.9 0.9": ["mistah"], "1.4 4.6 1.3": ["colposcope"], "17.5 38.0 8.4": ["strafes"], "-0.6 11.3 4.6": ["eicosanoids"], "5.9 -0.3 11.4": ["soundhole"], "-2.6 2.8 5.3": ["leukoencephalopathy"], "2.7 9.9 5.2": ["obas"], "1.2 11.9 10.9": ["ganglord"], "16.7 5.2 12.9": ["vulvas"], "5.3 22.4 8.4": ["bloviated"], "4.2 0.1 -1.1": ["buproprion"], "19.6 8.4 7.3": ["intralogistics"], "12.4 15.5 7.4": ["plutoid"], "-6.3 -5.3 13.6": ["ayis"], "2.2 4.2 15.9": ["plato"], "5.8 2.9 15.3": ["meredith"], "7.6 8.4 15.6": ["stockgrowers"], "20.4 8.0 20.2": ["firebrick"], "2.0 6.7 6.8": ["estamos"], "21.1 -0.0 7.6": ["recyled"], "19.2 10.0 17.6": ["moany"], "12.8 13.6 8.7": ["redshifted"], "5.2 1.1 10.2": ["hexachlorobenzene"], "2.5 10.6 5.2": ["soci"], "-1.4 5.3 3.7": ["vasomotor"], "-2.0 9.8 3.0": ["invidual"], "-4.0 11.3 3.3": ["forceable"], "0.1 0.7 1.3": ["livre"], "7.0 -0.5 9.5": ["neb"], "5.1 10.9 25.6": ["muay"], "0.8 35.1 7.3": ["weaponary"], "9.7 6.4 31.2": ["pasteles"], "17.3 8.3 17.4": ["rentiers"], "7.8 18.3 16.2": ["facedness"], "9.1 9.5 17.8": ["geoff"], "5.8 13.0 8.7": ["unclearly"], "-2.2 2.8 7.4": ["hospitalities"], "0.2 0.7 14.4": ["vigango"], "9.2 8.5 5.3": ["heliocentrism"], "4.8 8.3 7.8": ["plasmoid"], "17.0 12.1 26.0": ["astilbes"], "12.9 -0.0 36.0": ["sopas"], "32.6 11.9 21.4": ["candyland"], "-0.1 0.9 4.2": ["principales"], "6.0 14.6 9.8": ["pixellation"], "4.8 12.3 16.9": ["chuckholes"], "11.8 11.4 4.9": ["fettling"], "1.7 13.0 14.5": ["angiosarcoma"], "9.7 9.4 7.4": ["roadsweeper"], "8.4 18.7 4.4": ["meritocracies"], "0.4 5.3 6.4": ["thirdplace"], "9.7 3.8 10.9": ["noninsurance"], "9.1 -3.1 -4.2": ["sponsorless"], "-0.8 -1.1 -2.1": ["accessto"], "10.1 7.0 20.7": ["porridges"], "25.3 -6.4 2.6": ["sportwear"], "-2.9 2.8 11.0": ["basiliximab"], "-0.7 2.7 11.5": ["wildtype"], "11.2 -0.7 34.8": ["striploin"], "-0.1 10.8 12.1": ["nucleoprotein"], "7.4 13.1 6.8": ["wooer"], "16.5 13.3 19.8": ["eavestrough"], "-6.2 0.5 -0.7": ["ularitide"], "1.2 7.8 7.8": ["younsters"], "8.6 3.6 3.0": ["regie"], "16.3 14.0 20.9": ["itd"], "17.2 16.3 10.2": ["bamboozlement"], "-0.0 9.0 12.4": ["implimentation"], "2.4 6.1 13.0": ["unicorporated"], "0.2 -0.5 21.6": ["budwood"], "7.8 28.7 5.3": ["vengance"], "9.1 13.8 17.6": ["ades"], "11.0 16.5 14.7": ["kneeldowns"], "11.2 8.5 25.3": ["chandlers"], "-3.7 2.6 2.4": ["colostomies"], "1.9 8.3 7.8": ["methyltransferase"], "5.5 12.8 21.0": ["rosarians"], "-3.4 0.6 11.3": ["mentary"], "-3.0 15.4 4.3": ["thoughful"], "16.7 22.5 7.7": ["nefariousness"], "12.5 7.6 8.3": ["hardrive"], "8.4 10.7 20.2": ["felis"], "-4.5 5.1 -2.7": ["practicising"], "5.2 8.9 5.7": ["natio"], "2.8 -2.6 2.0": ["associatedwith"], "12.6 41.2 21.4": ["merchantmen"], "1.9 7.1 14.2": ["putonghua"], "1.1 7.2 6.8": ["mise"], "13.7 6.1 18.8": ["peggy"], "9.9 9.9 10.6": ["curandera"], "9.3 1.4 9.5": ["keer"], "11.3 16.2 11.5": ["nutbags"], "2.6 7.5 2.4": ["apeal"], "36.4 23.4 14.3": ["multiheaded"], "12.9 14.1 16.6": ["polyrhythm"], "0.5 13.3 11.2": ["intertextuality"], "15.8 5.5 4.2": ["dimiss"], "13.8 2.3 2.4": ["ninetieth"], "4.4 3.1 6.2": ["fopr"], "2.7 8.4 15.6": ["volvulus"], "0.4 16.2 -1.5": ["deprecates"], "6.5 0.5 10.0": ["arly"], "5.4 7.7 1.5": ["acquring"], "11.5 15.2 13.3": ["tunelessly", "phalange"], "14.4 17.2 11.3": ["acually"], "3.6 9.5 11.5": ["donorship"], "10.5 10.2 9.7": ["draggable"], "9.2 28.8 5.5": ["lumpenproletariat"], "10.2 -4.3 3.2": ["oleum"], "-4.9 4.7 1.9": ["acetazolamide"], "-1.1 4.0 6.3": ["tipstaff"], "4.4 10.1 8.9": ["bedwetters"], "8.3 11.3 26.1": ["corellas"], "-2.0 11.7 4.9": ["futureevents"], "11.0 5.5 10.7": ["superstud"], "10.4 17.1 6.8": ["sweethearting"], "6.0 17.3 16.3": ["chines"], "10.7 6.3 22.8": ["tinware"], "14.7 2.2 38.7": ["donburi"], "-9.3 6.1 -1.4": ["responsa"], "14.2 16.0 3.8": ["molue"], "10.2 8.5 21.8": ["sauvage"], "4.7 -2.9 4.3": ["hme"], "0.4 7.7 26.8": ["pitha"], "16.5 1.5 4.5": ["remerged"], "5.3 3.3 16.0": ["bearly"], "6.9 22.3 11.0": ["reductively"], "-1.8 4.9 2.3": ["gph"], "6.7 9.1 17.4": ["sandpile"], "8.7 6.0 2.7": ["minidisc"], "17.7 10.5 21.9": ["fingerpaint"], "5.5 29.4 13.9": ["shmups"], "2.8 4.5 0.6": ["elo"], "1.3 0.6 0.4": ["desipramine"], "-10.6 0.3 3.8": ["postintervention"], "6.2 4.3 2.1": ["jovoto"], "7.2 12.9 14.0": ["quaffers"], "0.1 8.3 3.9": ["actinolite"], "6.0 22.3 10.9": ["lickspittles"], "2.4 14.5 7.0": ["stablity"], "5.8 9.1 9.2": ["unmanageably"], "14.2 7.8 0.4": ["lactivists"], "-0.0 28.2 7.8": ["subclan"], "6.6 -4.0 5.3": ["reults"], "8.4 8.0 18.9": ["yeilds"], "4.7 7.3 9.7": ["countrie"], "4.6 10.3 10.5": ["manuevered"], "3.2 6.3 -2.1": ["microscopists"], "5.3 19.5 15.4": ["beaking"], "1.7 7.5 0.0": ["ultimatley"], "10.2 6.6 0.4": ["reacquires"], "-3.7 3.3 3.7": ["midodrine"], "-4.5 3.2 6.5": ["maintanance"], "15.6 7.7 9.1": ["carbonating"], "6.3 1.2 20.4": ["badam"], "0.9 6.2 9.2": ["ankerite"], "0.8 7.7 10.8": ["tibetan"], "11.5 -6.4 1.5": ["mondial"], "3.1 30.5 7.7": ["apostasies"], "7.0 7.6 -0.0": ["sanitisers"], "5.7 -3.0 5.8": ["laris"], "7.6 14.2 15.6": ["smilers"], "22.7 13.8 16.3": ["grot"], "6.9 8.1 13.2": ["jessie"], "6.7 10.9 17.0": ["blotchiness"], "1.0 11.2 8.5": ["relavant"], "9.4 22.9 16.9": ["propitiating"], "19.5 0.7 15.3": ["shwag"], "-8.6 16.5 9.2": ["tefillah"], "-1.5 23.1 3.0": ["authoritive"], "7.8 32.1 5.5": ["distracter"], "2.6 -7.0 0.8": ["deconversion"], "3.8 -1.9 10.8": ["sariling"], "0.2 -3.8 0.3": ["dez"], "-10.7 1.9 6.5": ["neostigmine"], "17.4 1.8 29.9": ["comal"], "5.8 7.4 1.7": ["liveblogs"], "9.4 -4.4 8.3": ["droppped"], "11.1 6.9 6.0": ["virtualises"], "13.6 6.6 10.5": ["peppiness"], "-0.6 12.6 9.9": ["snapshooters"], "12.4 37.2 3.3": ["brownshirt"], "3.2 8.2 11.5": ["stylistas"], "7.1 19.1 11.2": ["neurasthenic"], "8.5 -2.5 23.8": ["ewa"], "11.4 12.7 22.4": ["circumnavigator"], "10.1 10.5 3.2": ["lenovo"], "7.0 3.1 9.1": ["sonication"], "9.7 13.3 14.8": ["glycoside"], "14.4 7.8 28.0": ["planarian"], "1.4 12.2 10.2": ["eres"], "9.8 -3.6 8.4": ["prohormones"], "22.8 -0.0 18.9": ["sweatered"], "14.5 17.1 33.3": ["longbeard"], "18.5 12.1 15.1": ["surliest"], "5.6 -0.2 9.2": ["interbody"], "4.1 9.0 7.0": ["dispossessions"], "3.9 11.8 4.9": ["xenobiotics"], "3.5 8.6 13.1": ["fantaserye"], "21.7 12.5 38.7": ["gaffing"], "1.5 5.0 17.2": ["cyc"], "8.7 -4.9 -2.8": ["siging"], "3.5 7.5 3.1": ["multidomain"], "2.2 11.0 11.3": ["monoamines"], "8.4 4.0 9.6": ["skyed"], "3.1 6.5 7.8": ["demagnetization"], "13.6 20.3 24.4": ["rheumy"], "10.4 8.6 11.4": ["scruffs"], "-3.7 16.3 4.3": ["contd"], "-0.6 5.9 12.1": ["subclavian"], "17.2 14.0 15.0": ["frowny"], "-5.7 0.0 10.4": ["norma"], "11.6 7.1 28.6": ["rustica"], "3.8 14.4 12.0": ["cesc"], "10.5 14.5 8.2": ["drenchings"], "15.1 7.4 29.1": ["pomme"], "1.7 6.1 11.3": ["mosaicism"], "9.1 10.2 22.9": ["shikaras"], "-5.4 12.0 7.0": ["counciling"], "-3.1 4.9 16.5": ["ptr"], "10.3 5.8 -3.4": ["tonometer"], "1.7 7.6 28.0": ["ulam"], "-6.8 11.6 13.6": ["subareas"], "19.1 2.9 3.7": ["plannning"], "0.8 7.7 8.3": ["bexarotene"], "-2.3 10.7 -4.8": ["shewas"], "10.2 14.5 12.2": ["underquoting"], "16.6 -5.3 9.2": ["surrouding"], "0.7 6.2 6.2": ["bibliotherapy"], "-2.3 15.4 12.9": ["normalness"], "2.0 6.0 5.3": ["motorcylists"], "9.6 8.7 13.3": ["eile"], "6.7 19.3 12.9": ["polcie"], "4.8 10.1 4.0": ["foundationally"], "5.5 -1.0 20.4": ["cheffing"], "11.1 29.2 5.8": ["theocons"], "4.3 1.8 -0.0": ["underconstruction"], "12.9 15.2 27.9": ["ironweed"], "16.5 3.1 15.8": ["lisence"], "1.7 22.3 2.7": ["panthic"], "6.7 10.3 -0.3": ["cubeless"], "1.0 7.9 5.1": ["appaled"], "15.3 10.0 10.5": ["belling"], "21.6 5.1 25.9": ["fricasseed"], "15.4 7.4 5.1": ["infrastrucutre"], "-4.3 8.9 8.9": ["vacinity"], "4.9 20.7 2.8": ["cyberstalker"], "-2.9 3.0 8.0": ["neurohormonal"], "9.1 14.2 8.9": ["ufology"], "15.4 2.5 18.7": ["eventgoers"], "8.6 26.0 19.1": ["breathin"], "4.0 12.1 2.8": ["glummer"], "13.2 17.3 18.1": ["canucks"], "10.3 5.7 13.2": ["frankie"], "8.8 16.4 14.7": ["salinomycin"], "-9.9 -3.2 4.4": ["konkani"], "20.7 5.5 22.5": ["frappucino"], "8.2 20.1 24.4": ["sunscald"], "-5.4 -2.4 -4.2": ["clubfitting"], "5.2 10.8 2.8": ["yagnas"], "2.3 9.7 1.8": ["alllowed"], "2.5 -4.8 0.4": ["developmentof"], "12.3 2.4 16.9": ["ags"], "-2.9 6.2 4.4": ["upsold"], "8.8 7.9 9.1": ["sexaholic"], "6.8 7.5 7.5": ["propert"], "16.8 21.7 14.7": ["batcave"], "-3.0 2.9 7.5": ["mailpieces"], "5.5 15.0 10.4": ["devouts"], "9.5 9.4 11.7": ["sars"], "7.5 0.3 17.3": ["liposuctioned"], "2.6 10.4 11.7": ["endocytic"], "4.7 6.9 5.7": ["atheletic"], "1.0 15.3 6.1": ["oficers"], "-2.3 15.5 2.5": ["valorized"], "-4.5 0.6 -4.2": ["arap"], "5.0 10.4 13.2": ["hedonics"], "0.1 24.1 3.5": ["missioned"], "2.4 1.6 5.9": ["familie"], "9.8 22.6 11.5": ["agni"], "1.6 23.1 1.4": ["recee"], "4.9 11.2 27.2": ["eew"], "1.5 15.0 6.7": ["accidential"], "1.3 10.4 10.1": ["outpass"], "2.3 5.8 5.6": ["stafford"], "9.8 7.2 19.8": ["ernie"], "6.4 18.6 9.9": ["unecessarily"], "1.3 2.9 14.5": ["dette"], "5.1 2.9 27.6": ["pummelo"], "0.9 -3.3 -3.4": ["officialized"], "1.0 10.9 7.3": ["retreatants"], "17.2 39.7 15.1": ["psionic"], "12.3 15.7 23.8": ["mycelia"], "22.4 7.2 5.8": ["wunder"], "5.6 13.5 6.9": ["likly"], "11.2 9.1 13.1": ["prestin"], "1.3 11.7 10.0": ["universalised"], "22.2 31.0 18.5": ["hellspawn"], "9.5 4.0 9.0": ["biodigesters"], "-0.8 11.3 12.4": ["hatao"], "4.9 9.0 5.0": ["transecting"], "20.3 3.8 12.9": ["bukkake"], "18.0 6.5 13.4": ["restacking"], "12.7 2.1 10.2": ["nightdresses"], "6.7 1.4 36.6": ["sevruga"], "-7.1 15.4 1.1": ["thses"], "-2.8 2.8 3.5": ["hemofiltration"], "10.1 2.9 14.1": ["briquetting"], "16.0 18.9 9.0": ["oxymoronically"], "9.2 5.3 8.6": ["rowdily"], "6.7 11.8 8.6": ["remobilizing"], "-2.0 7.6 1.8": ["multidisciplined"], "8.2 13.8 6.3": ["customisability"], "-3.4 11.6 10.9": ["colorfastness"], "5.0 0.7 15.8": ["bim"], "15.1 2.7 8.5": ["undercounter"], "6.2 -1.7 -5.3": ["ogy"], "11.9 13.4 14.0": ["paragneiss"], "14.1 6.4 29.8": ["tajine"], "5.5 0.6 15.4": ["eisteddfods"], "0.5 -0.6 6.7": ["passported"], "5.0 20.8 18.0": ["litterer"], "12.2 4.1 10.8": ["tracheas"], "14.0 7.7 18.6": ["slenderizing"], "12.9 14.0 16.5": ["massifs"], "17.3 11.5 -1.4": ["monoply"], "10.1 24.0 17.8": ["equably"], "12.7 15.3 16.2": ["thuddingly"], "12.6 20.0 18.6": ["jemagee"], "3.8 9.1 20.5": ["etymologist"], "19.1 0.3 14.9": ["thermoform"], "5.9 -3.2 8.1": ["preisvergleich"], "12.4 2.9 7.3": ["marquess"], "-3.7 10.4 9.4": ["myoclonus"], "4.1 10.5 18.9": ["saan"], "-3.1 3.6 -3.8": ["haemodynamic"], "4.2 21.3 1.6": ["subserve"], "5.5 6.6 13.9": ["bagay"], "18.7 6.0 11.1": ["corrugating"], "5.4 7.2 6.2": ["dressup"], "-8.4 9.7 8.9": ["soco"], "11.4 23.9 3.4": ["caliphates"], "10.5 13.1 35.5": ["cuda"], "8.6 9.4 9.5": ["hydrometeorological"], "1.4 1.1 6.5": ["preceptorships"], "1.9 4.7 4.8": ["autocrine"], "-1.3 8.0 10.9": ["granulomatous"], "7.9 9.2 7.6": ["wheelmen"], "-1.2 13.4 5.6": ["tresspass"], "3.9 23.4 7.5": ["chosenness"], "10.3 8.3 7.1": ["mobe"], "12.4 11.4 11.0": ["reclosing"], "4.6 4.8 7.9": ["antiskid"], "-5.0 9.2 1.5": ["englandfans"], "2.5 7.6 3.8": ["trailways"], "14.4 16.2 13.4": ["basenji"], "3.5 -4.0 1.3": ["msp"], "2.3 17.1 4.4": ["tommasse"], "3.4 21.6 16.1": ["spics"], "16.2 10.1 23.4": ["slushing"], "4.9 12.9 -0.2": ["intragovernmental"], "11.9 17.1 8.4": ["circularly"], "5.1 6.0 7.1": ["mbt"], "1.4 5.9 18.7": ["magmatism"], "5.4 14.1 18.5": ["fleshtones"], "-3.8 3.3 0.7": ["reviewal"], "9.7 0.9 -3.3": ["calorimeters"], "-3.7 7.7 11.3": ["undervoting"], "10.8 -0.7 -11.1": ["headoffice"], "5.2 5.6 12.2": ["afetr"], "1.4 6.9 -1.8": ["empolis"], "5.9 -2.9 10.2": ["approximatly"], "-4.1 -4.3 3.7": ["clinicaltrials"], "9.6 11.1 9.2": ["hansen"], "2.5 7.5 0.9": ["newspaperwoman"], "3.1 9.4 11.7": ["naye"], "5.7 7.7 6.3": ["scart"], "1.4 6.5 13.8": ["phenological"], "6.9 12.3 12.9": ["gret"], "14.8 -0.8 1.0": ["sihk"], "-3.4 11.4 13.2": ["agronomically"], "7.9 10.4 -0.6": ["palying"], "-3.5 0.6 -0.7": ["discusion"], "6.2 0.4 13.2": ["upin"], "8.5 23.6 12.6": ["aforethought"], "6.4 13.6 22.6": ["sclerotia"], "-0.5 11.5 -1.1": ["noninvolvement"], "9.0 18.7 5.5": ["cellsite"], "16.3 5.2 16.6": ["preprocessed"], "-1.8 7.4 5.9": ["arthropathy"], "7.1 12.6 1.8": ["convential"], "6.0 10.2 20.4": ["nooner"], "15.1 1.8 5.3": ["opeing"], "28.2 7.7 21.4": ["tushie"], "15.8 9.4 13.9": ["jacka"], "6.2 14.0 6.0": ["pricklier"], "12.7 9.7 6.3": ["ultimo"], "-5.3 9.6 9.6": ["novitiates"], "20.4 4.8 43.6": ["ceps"], "28.2 1.4 24.4": ["thighed"], "8.2 16.5 16.6": ["crosshatching"], "2.8 6.8 7.2": ["diabulimia"], "1.9 8.2 21.0": ["agama"], "13.1 15.7 15.4": ["astrolabes"], "0.6 8.0 3.2": ["epoxide"], "2.4 5.9 3.7": ["vidoes"], "2.3 11.2 -0.5": ["padyatras"], "1.5 15.3 4.8": ["commom"], "4.4 8.9 7.2": ["girliest"], "15.5 13.5 10.9": ["outthe"], "6.4 2.7 5.8": ["greenkeeping"], "-1.6 0.6 9.6": ["hairloss"], "6.4 11.9 3.6": ["dishtv"], "23.3 14.9 7.4": ["ingeniousness"], "4.8 9.4 2.8": ["calorimetry"], "5.1 6.5 14.6": ["stipes"], "6.8 6.0 15.8": ["baylands"], "-0.5 -0.3 4.3": ["excimer"], "9.8 24.5 13.2": ["streetfighting"], "7.3 33.9 10.1": ["idolators"], "8.2 11.5 33.8": ["succulently"], "-4.0 0.1 14.0": ["pagiging"], "15.5 15.5 26.1": ["ringlet"], "21.1 0.5 11.7": ["cafi"], "5.5 1.6 -0.2": ["muscians"], "14.1 10.5 9.8": ["sunlamp"], "19.4 4.1 12.1": ["fingerpainting"], "6.3 2.9 11.5": ["chirpier"], "1.2 -1.0 7.9": ["esterified"], "0.5 14.1 -5.3": ["orality"], "14.4 15.0 8.5": ["astrobiological"], "15.1 -0.3 3.2": ["philanthropical"], "3.7 -3.1 0.4": ["nique"], "19.1 -2.0 5.6": ["gatefolds"], "4.3 12.8 1.1": ["quaterfinal"], "1.0 -1.4 8.7": ["gestations"], "12.0 17.5 13.1": ["smarks"], "6.8 9.5 18.8": ["ginkgoes"], "-2.2 21.6 5.2": ["disipline"], "-1.8 -7.9 0.4": ["completeing"], "-5.1 1.7 1.9": ["desflurane"], "-4.5 1.9 2.2": ["amprenavir"], "2.7 -3.7 13.6": ["algunas"], "10.5 10.0 10.0": ["tranport"], "14.3 7.8 -0.1": ["instituions"], "10.7 20.0 19.0": ["mutualistic"], "5.3 -3.2 0.8": ["highback"], "9.0 0.2 16.8": ["betacarotene"], "-1.3 12.7 4.8": ["punkbands"], "2.5 2.6 12.6": ["jor"], "1.6 9.4 10.4": ["familias"], "7.1 13.3 12.8": ["dha"], "-1.3 2.2 6.4": ["concertante"], "-0.5 5.9 2.2": ["governers"], "-2.8 17.9 2.4": ["detribalized"], "4.7 0.7 7.2": ["orthophotography"], "16.3 10.2 36.1": ["snowcone"], "-5.5 12.2 7.7": ["abandoners"], "-3.0 4.1 -4.3": ["atrexx"], "7.4 10.5 -0.2": ["conrol"], "11.3 4.9 11.4": ["recycleable"], "4.9 2.4 11.0": ["amides"], "1.3 11.3 7.1": ["downregulate"], "0.9 -0.6 -5.9": ["dla"], "8.0 1.5 25.6": ["vinos"], "1.6 2.2 0.8": ["agomelatine"], "2.7 -7.9 4.6": ["recommened"], "21.9 8.2 14.7": ["hoggers"], "-2.1 1.4 -2.1": ["admnistration"], "4.4 12.7 8.0": ["wto"], "-5.7 2.2 15.1": ["lge"], "15.2 13.5 8.9": ["detroyed"], "19.8 16.2 35.9": ["lipless"], "-1.0 7.8 22.1": ["bato"], "20.5 19.8 5.7": ["kremlin"], "9.2 3.2 19.9": ["aquathon"], "-2.2 -6.5 8.5": ["rebonding"], "14.7 10.5 8.5": ["hyperinflated"], "3.5 10.1 14.4": ["nonpathogenic"], "4.0 6.7 9.0": ["sublingually"], "-5.8 9.7 14.9": ["galactosemia"], "7.0 4.8 5.0": ["rejuvinate"], "7.5 0.4 12.6": ["showfield"], "-2.5 2.0 8.0": ["propers"], "18.5 18.2 19.8": ["freakazoid"], "1.6 4.8 11.8": ["noninflationary"], "1.2 -3.1 12.6": ["eport"], "-0.4 2.0 -0.9": ["cordinator"], "-3.5 4.6 5.7": ["hechsher"], "17.3 20.9 14.5": ["superabundant"], "-1.0 3.2 6.1": ["kathas"], "5.0 14.8 11.2": ["uxorious"], "18.7 8.9 15.2": ["caduceus"], "2.6 4.5 17.1": ["regressively"], "17.8 19.3 8.3": ["manacle"], "12.0 -0.8 10.8": ["busine"], "-5.3 2.9 4.8": ["atlarge"], "-6.8 -4.3 6.4": ["expungements"], "4.2 -1.2 17.7": ["pigeonpea"], "-5.5 9.4 20.6": ["equids"], "7.6 10.2 13.4": ["fracases"], "-4.9 1.9 3.3": ["resits"], "6.8 -0.7 10.0": ["hardhit"], "-0.8 8.2 11.8": ["aapke"], "6.9 7.0 21.0": ["clubbin"], "7.3 17.7 14.7": ["coulrophobia"], "3.3 13.4 11.2": ["exogenously"], "5.1 23.0 4.8": ["bootheel"], "-0.9 12.5 10.1": ["setuid"], "5.3 7.6 14.6": ["catergories"], "19.5 -2.3 11.5": ["giveways"], "6.3 -1.2 1.7": ["coachbuilding"], "6.6 13.8 32.7": ["jook"], "7.0 1.3 2.5": ["eyedrop"], "1.4 -3.6 16.0": ["noncelebrity"], "12.0 1.1 10.6": ["upp"], "14.4 -11.2 4.4": ["corrugator"], "-1.4 8.3 5.1": ["bhasha"], "2.8 2.1 5.1": ["nanoemulsions"], "7.6 3.2 -1.5": ["championhip"], "12.0 5.4 8.0": ["heps"], "2.4 3.6 13.0": ["ecolodge"], "5.7 19.4 4.3": ["activex"], "17.7 8.5 5.1": ["iffic"], "-10.7 0.7 3.5": ["scorings"], "7.7 6.1 12.9": ["zoe"], "11.2 21.1 -1.5": ["lionising"], "8.5 5.6 6.0": ["junketeers"], "18.9 18.6 15.0": ["bioelectric"], "-4.3 15.9 -2.4": ["assister"], "4.8 20.5 6.5": ["undaunting"], "6.9 4.3 12.2": ["mesures"], "17.9 7.9 27.6": ["chompin"], "-1.4 7.8 -1.4": ["intralesional"], "10.4 11.3 1.2": ["borefest"], "6.0 23.5 5.5": ["camers"], "-2.0 17.6 7.7": ["filterable"], "4.4 4.6 1.4": ["lassen"], "-3.8 10.2 6.3": ["experiece"], "6.5 14.7 11.8": ["similarexpressions"], "2.1 10.5 9.4": ["scholasticism"], "2.5 17.7 20.5": ["wireworm"], "7.4 9.7 8.6": ["cyberchondriacs"], "-2.2 3.2 10.4": ["agb"], "-3.9 4.9 4.9": ["proband"], "8.9 -0.4 0.1": ["quarer"], "10.6 6.6 -1.8": ["videomail"], "5.4 4.8 24.9": ["nonmeat"], "1.8 6.9 12.7": ["pion"], "7.5 13.7 2.3": ["notifiers"], "2.6 6.6 15.9": ["sinabi"], "18.6 3.9 27.4": ["cheetos"], "13.8 -0.6 9.5": ["cosmeticians"], "8.9 10.5 16.2": ["copula"], "7.6 17.2 17.1": ["dajafi"], "5.2 9.9 6.0": ["poing"], "9.2 10.3 20.5": ["shortselling"], "7.3 16.6 1.6": ["puristic"], "13.5 2.2 39.3": ["chipolatas"], "16.6 4.3 7.4": ["mfrs"], "0.2 2.1 5.1": ["canticles"], "18.8 11.6 9.3": ["switchyards"], "5.3 6.9 9.2": ["methylenedioxymethamphetamine"], "11.8 10.2 10.7": ["fillin"], "2.2 12.5 13.0": ["sanenazok"], "1.2 12.2 4.8": ["acknowleges"], "19.7 12.5 10.6": ["telstra"], "-4.0 14.4 5.5": ["khimar"], "7.3 25.9 20.4": ["windshifts"], "1.5 15.3 1.9": ["foregin"], "6.9 5.1 8.7": ["deci"], "5.7 0.1 10.6": ["parkinson"], "11.2 16.9 9.8": ["deoderant"], "8.9 4.3 9.5": ["loooking"], "16.5 10.0 3.4": ["logisitics"], "17.4 14.3 4.0": ["profiteered"], "13.6 6.1 13.3": ["kingsize"], "-4.2 2.8 9.0": ["mmb"], "10.7 10.3 8.0": ["zippiest"], "3.7 1.3 27.7": ["fastnachts"], "-4.8 -2.0 -3.4": ["pyschiatric"], "7.5 11.8 18.4": ["lepidoptera"], "7.2 16.7 12.7": ["jelous"], "10.4 8.2 18.0": ["fouettes"], "19.8 23.0 25.4": ["jabberwocky"], "6.8 6.3 7.4": ["retrocessions"], "9.5 9.6 35.2": ["skordalia"], "0.3 7.8 9.8": ["discrimation"], "0.2 3.7 5.9": ["relaxants"], "6.1 10.0 3.4": ["supprt"], "2.4 18.9 5.1": ["disgruntle"], "10.0 3.9 13.5": ["levi"], "18.8 11.1 17.8": ["bottlecaps"], "16.7 4.0 19.8": ["pinkest"], "0.9 2.9 15.0": ["negosyo"], "10.0 12.9 22.2": ["matkas"], "10.2 9.3 16.9": ["satori"], "9.6 10.0 13.3": ["divinations"], "3.3 9.4 11.8": ["rit"], "-0.6 11.1 -1.0": ["harrased"], "-2.9 6.8 11.4": ["oligodendroglioma"], "8.0 6.2 27.2": ["firkins"], "12.3 6.0 9.7": ["peacocking"], "-1.0 6.5 -1.2": ["partyline"], "1.1 19.6 11.7": ["unmannerly"], "-6.0 23.6 18.3": ["tarries"], "18.6 4.0 24.6": ["ouncers"], "7.3 4.5 7.9": ["gauzes"], "-0.6 4.9 11.7": ["fibrosarcoma"], "8.4 4.8 7.2": ["bldgs"], "9.9 5.8 4.0": ["quadraphonic"], "-3.2 2.5 7.2": ["misdeameanor"], "1.9 12.1 3.3": ["empaneling"], "-2.6 6.7 3.0": ["akims"], "8.7 13.3 7.5": ["isobutene"], "-2.2 13.7 -4.1": ["acknowleding"], "2.0 12.8 12.5": ["weightclass"], "15.9 1.2 14.7": ["coved"], "1.8 13.0 10.0": ["weeker"], "12.0 9.0 9.8": ["naffness"], "-3.5 1.5 7.6": ["sargramostim"], "4.0 24.1 6.7": ["outschemed"], "17.0 11.5 24.1": ["candytuft"], "10.8 9.5 8.8": ["gasketed"], "11.0 7.2 4.4": ["gymnasia"], "12.0 9.5 9.1": ["mythbusters"], "15.0 13.4 23.9": ["mistletoes"], "9.4 1.9 14.3": ["saddlebreds"], "4.1 11.6 9.1": ["mju"], "7.7 24.1 6.3": ["sophistries"], "2.1 3.5 15.7": ["kilala"], "4.5 7.3 11.3": ["meteorol"], "-7.1 6.2 -2.5": ["timebound"], "2.6 8.1 7.9": ["straightlaced"], "9.2 0.7 7.5": ["flossers"], "10.5 5.0 -0.7": ["codevelopment"], "2.6 3.0 13.2": ["kaba"], "6.1 7.6 20.7": ["centrifuging"], "4.2 8.4 12.9": ["glycolytic"], "-11.1 -0.8 0.6": ["certificants"], "16.0 12.4 15.4": ["blousons"], "-1.8 11.2 9.0": ["kitna"], "1.1 7.7 18.5": ["trapshoot"], "13.0 6.9 15.6": ["grillmaster"], "-1.9 -7.5 4.5": ["forerunning"], "9.1 9.6 6.0": ["delocalized"], "21.5 8.9 14.5": ["gawdawful"], "1.0 8.5 -2.6": ["strengthing"], "8.8 -2.1 9.9": ["cataloguers"], "4.3 -10.8 -3.0": ["extenstion"], "4.2 10.1 16.1": ["tehzeeb"], "-5.8 13.1 4.5": ["examinable"], "1.6 19.6 9.3": ["backstabs"], "7.3 9.8 27.1": ["floatables"], "-0.0 21.3 12.1": ["siutation"], "7.3 9.7 7.0": ["polarimetric", "familier"], "4.9 10.3 16.0": ["organo"], "3.0 5.1 30.8": ["crayfishing"], "20.2 23.5 25.8": ["glowworms"], "-2.3 19.9 2.7": ["supected"], "6.9 8.1 13.4": ["contigs"], "0.5 11.7 -0.4": ["murdabad"], "9.1 12.2 13.6": ["buidings"], "14.4 5.6 6.5": ["derisked"], "3.1 17.0 9.9": ["sitation"], "15.0 16.3 15.5": ["shinpad"], "14.7 -1.1 23.9": ["bandz"], "-15.1 0.9 6.9": ["exceptionalities"], "-2.0 9.0 18.7": ["theresa"], "2.5 6.1 9.6": ["classwide"], "17.7 16.8 25.3": ["eiderdown"], "14.6 5.4 10.1": ["roadbuilders"], "3.9 11.2 5.3": ["servicewide"], "12.5 40.4 18.7": ["terran"], "-3.3 -0.1 5.3": ["olan"], "1.9 8.8 14.2": ["ballplaying"], "2.1 13.1 7.3": ["consubstantial"], "7.7 2.4 10.2": ["postdate"], "-1.8 6.7 -2.5": ["scrunity"], "10.1 -5.2 8.4": ["lade"], "11.9 9.5 17.6": ["fallaways"], "7.1 14.0 10.0": ["elatedly"], "2.0 4.1 7.7": ["anders"], "3.2 22.1 3.4": ["enosis"], "3.3 4.6 4.9": ["semble"], "9.8 16.4 1.4": ["deflagration"], "9.7 5.9 15.0": ["cageless"], "4.7 8.5 11.5": ["lifestyling"], "17.8 2.9 9.2": ["switcharoo"], "10.5 9.8 7.1": ["ishtyle"], "0.6 8.1 3.3": ["yolink"], "-2.2 8.5 8.0": ["steatohepatitis"], "24.0 17.5 0.7": ["flashmobs"], "5.7 9.3 21.7": ["muskmelons"], "-1.4 16.7 1.1": ["advantange"], "1.5 5.8 6.6": ["theentire"], "19.6 16.5 35.6": ["arapaima"], "6.3 11.0 14.0": ["mikey"], "1.3 21.6 2.1": ["legimate"], "7.1 8.4 12.9": ["denmark"], "3.5 12.5 5.7": ["globetrot"], "-2.8 15.2 11.9": ["safetly"], "5.3 4.1 3.1": ["dataloggers"], "15.0 11.5 13.1": ["blanky"], "-3.1 -5.5 14.6": ["nonmandatory"], "0.9 13.7 -1.3": ["namechecking"], "0.7 13.4 7.7": ["ican"], "24.1 -5.1 -0.2": ["indsutry"], "13.5 22.2 36.4": ["blacktail"], "21.4 2.7 40.7": ["saltine"], "-3.5 -4.1 1.4": ["nte"], "-5.8 -1.7 6.0": ["reimplement"], "-4.0 3.4 2.7": ["synodal"], "20.0 9.6 20.7": ["candling"], "3.0 9.4 -1.1": ["collocating"], "8.6 12.7 12.7": ["upflow"], "0.5 5.5 -1.1": ["bandies"], "13.2 36.6 19.5": ["flashbangs"], "6.4 7.1 15.8": ["vanillas"], "1.1 -9.2 0.5": ["communitybased"], "16.0 3.7 8.3": ["oid"], "4.6 7.2 10.3": ["polyphenolic"], "4.6 1.3 2.4": ["hightlights"], "9.7 5.1 18.3": ["brrrr"], "4.5 18.3 7.9": ["miscontrol"], "13.9 11.6 13.7": ["unlace"], "4.5 2.8 -4.2": ["performanc"], "7.4 9.6 21.0": ["podded"], "12.7 23.5 12.2": ["outpunch"], "2.2 -1.2 3.5": ["sinetron"], "3.7 31.2 15.2": ["midsts"], "17.3 18.9 11.4": ["waterbomber"], "3.2 9.4 12.5": ["fet"], "5.8 13.6 5.0": ["juz"], "9.0 12.6 7.1": ["differe"], "-4.2 11.9 8.1": ["reinsureds"], "12.6 -2.5 -0.1": ["erp"], "-0.1 23.5 5.1": ["personalism"], "4.9 6.2 -0.8": ["medios"], "-1.0 14.4 12.0": ["sasural"], "6.8 2.8 -0.9": ["sevenload"], "-0.1 10.4 11.1": ["entonces"], "15.4 12.0 21.0": ["byre"], "-2.8 15.1 8.3": ["nawettan"], "5.4 26.6 17.3": ["daimyo"], "10.2 13.6 12.4": ["leicester"], "5.8 5.4 18.9": ["hyperphagia"], "9.9 9.3 6.5": ["exa"], "11.1 10.0 21.2": ["mollis"], "4.0 17.1 3.7": ["dogtag"], "13.6 14.9 15.4": ["dogpiled"], "2.2 9.6 12.2": ["avidin"], "12.7 4.5 4.4": ["underproducing"], "20.5 7.1 11.0": ["carrys"], "12.4 15.8 15.7": ["tetrahedra"], "6.1 -1.7 2.8": ["hwi"], "-2.6 -1.5 1.2": ["bifunctional"], "6.5 19.8 7.2": ["stammerers"], "2.2 3.7 8.4": ["pinouts"], "4.6 12.9 14.8": ["agilities"], "9.1 -3.9 7.7": ["supension"], "6.6 4.4 7.1": ["actigraph"], "0.1 1.5 13.5": ["houseowner"], "9.3 5.9 8.6": ["tripartisan"], "0.3 3.3 12.7": ["knox"], "6.4 0.8 10.4": ["modularisation"], "8.1 -15.6 7.6": ["incuded"], "12.5 19.1 9.7": ["serratia"], "11.9 8.8 12.6": ["nonsequel"], "7.6 8.9 17.2": ["kern"], "9.7 -3.3 17.7": ["naturellement"], "1.8 0.1 11.1": ["domaines"], "4.4 3.4 8.8": ["kilowatthours"], "-6.0 5.5 11.7": ["acter"], "-13.8 2.5 -0.2": ["compet"], "-3.1 9.8 5.0": ["sayid"], "0.5 9.1 0.4": ["uti"], "10.0 5.2 11.5": ["mackintosh"], "8.8 33.9 16.4": ["insensibly"], "6.4 -2.3 0.9": ["nivel"], "7.8 8.0 6.2": ["oversexualized"], "-3.1 -1.7 0.4": ["extened"], "14.1 15.5 5.2": ["teamup"], "9.1 16.2 5.8": ["inversed"], "1.8 1.1 4.3": ["reneg"], "16.1 0.6 41.5": ["braciole"], "6.9 7.9 7.4": ["wyoming"], "13.5 3.2 12.9": ["uw"], "6.4 10.2 1.9": ["sportily"], "2.0 21.6 4.5": ["witth"], "-3.0 9.9 3.7": ["reflexion"], "10.1 2.8 35.2": ["popiah"], "3.9 8.6 3.8": ["aleo"], "2.3 4.8 3.4": ["cedulas"], "20.4 12.2 13.8": ["proverbials"], "11.3 4.6 -1.9": ["txtr"], "6.7 6.6 8.0": ["panelbeater"], "-6.3 0.0 3.7": ["chorioamnionitis"], "12.3 -1.6 2.8": ["carrycot"], "6.3 12.6 5.3": ["weatherhead"], "7.5 1.0 15.9": ["rondalla"], "18.4 0.9 10.2": ["cartoning"], "14.4 16.5 18.9": ["zonk"], "0.7 11.4 4.1": ["standardizations"], "9.7 2.2 12.5": ["funfilled"], "-0.4 20.5 16.3": ["operandi"], "12.9 -0.9 13.4": ["myers"], "1.9 15.9 8.3": ["overinterpreting"], "3.9 12.1 11.9": ["achcha"], "14.9 -0.8 -3.5": ["andmarketing"], "-5.6 0.6 14.6": ["chimis"], "-0.6 3.5 14.4": ["copings"], "5.6 8.7 -1.8": ["bck"], "9.6 15.6 5.0": ["sault"], "16.9 9.5 20.3": ["fatboy"], "2.5 12.1 2.5": ["qoute"], "1.0 10.0 8.6": ["sowohl"], "-2.5 4.8 8.0": ["neal"], "4.6 7.2 13.7": ["mosaicking"], "-9.7 5.6 9.0": ["dysphoric"], "8.3 12.4 24.1": ["tabasco"], "7.6 19.9 5.5": ["antiseptically"], "4.3 1.9 -2.8": ["apppointed"], "20.1 6.9 6.8": ["infall"], "14.4 26.5 6.7": ["bodyslamming"], "8.0 28.0 17.0": ["pakis"], "-3.8 12.0 16.3": ["katotohanan"], "-0.3 3.1 11.2": ["stayover"], "8.1 2.6 7.9": ["farecard"], "7.0 12.9 8.7": ["overextends"], "13.8 13.3 17.4": ["passeggiata"], "9.3 12.7 28.1": ["insectivorous"], "4.2 18.4 14.1": ["unbury"], "1.3 17.7 17.5": ["barranca"], "0.6 12.1 8.4": ["thoes"], "0.2 0.2 9.6": ["roadeo"], "15.2 4.5 14.9": ["sherman"], "2.2 12.5 3.6": ["guility"], "-4.3 6.1 6.2": ["ually"], "21.0 5.1 2.7": ["xerography"], "0.9 4.6 0.3": ["accute"], "-6.5 8.1 4.1": ["presbyterate"], "4.9 2.8 3.9": ["outearn"], "9.5 12.3 30.0": ["cucurbit"], "0.3 3.6 21.9": ["kaitiaki"], "19.5 12.2 35.6": ["auk"], "2.7 6.6 2.9": ["equilibrated"], "6.6 9.3 9.8": ["choon"], "22.4 15.5 31.6": ["rusticles"], "9.6 11.0 12.8": ["giftwrapped"], "5.8 6.2 19.3": ["unlimiteds"], "1.5 0.7 -5.9": ["lyceums"], "3.0 7.2 13.1": ["miniplug"], "3.7 -1.2 15.7": ["luis"], "8.9 7.2 15.1": ["vermont"], "14.4 13.9 18.5": ["bicuspids"], "12.9 5.4 8.5": ["postdates"], "8.6 20.4 28.7": ["beadhead"], "2.3 22.0 7.6": ["cooperativism"], "8.6 15.9 -1.3": ["samething"], "-5.6 4.9 7.3": ["seropositivity"], "7.2 5.1 1.4": ["eneded"], "8.1 3.9 17.9": ["stapes"], "-7.6 -2.0 -1.9": ["particiapte"], "1.0 1.2 9.6": ["pyschology"], "4.5 7.2 3.2": ["stiffle"], "0.7 20.4 15.0": ["overprotecting"], "-6.2 5.0 -1.1": ["nonphysicians"], "-1.7 3.9 10.5": ["jud"], "5.6 7.2 8.9": ["homam"], "12.6 1.6 10.9": ["bikepath"], "20.2 15.9 13.7": ["dreamboats"], "4.9 16.6 9.1": ["philosophise"], "13.7 16.3 13.9": ["flabs"], "8.2 21.8 7.8": ["aviod"], "2.5 3.6 29.8": ["skimboarders"], "10.0 9.2 -1.0": ["portably"], "-1.4 3.8 8.1": ["gonzales"], "27.1 19.7 16.8": ["hulked"], "5.2 23.0 3.5": ["reify"], "5.6 1.9 11.9": ["lolita"], "26.3 10.7 13.7": ["brawniest"], "9.9 17.0 3.0": ["inhospitality"], "-9.9 2.7 10.4": ["reenroll"], "9.3 7.4 6.8": ["cbanker"], "-4.0 -2.4 7.5": ["housetype"], "2.6 21.0 8.5": ["rejecters"], "3.0 11.7 8.6": ["defensmen"], "2.3 26.6 7.3": ["posistion"], "8.8 19.5 11.8": ["liber"], "6.4 18.5 8.1": ["youhave"], "3.1 -0.3 1.9": ["tii"], "17.5 10.5 34.8": ["oarfish"], "3.3 -6.3 -3.1": ["offereing"], "0.8 -1.4 3.9": ["financ"], "13.9 19.5 10.1": ["schlockmeister"], "-5.0 -0.1 3.3": ["explantation"], "3.8 13.4 4.6": ["attitute"], "20.3 12.4 21.7": ["knobbed"], "23.3 22.7 27.5": ["chitons"], "-5.2 13.0 15.8": ["phoma"], "14.1 5.9 33.5": ["salade"], "0.6 13.9 11.0": ["mythologist"], "3.8 21.6 4.8": ["defriended"], "1.1 7.5 4.9": ["qs"], "4.1 1.2 4.2": ["exgratia"], "14.1 18.1 11.8": ["tada"], "5.9 25.4 14.5": ["cauterised"], "3.0 6.4 14.2": ["katherine"], "9.1 8.1 19.1": ["drumlin"], "10.5 11.9 8.0": ["malcontented"], "-3.4 10.7 15.0": ["hustla"], "16.2 2.2 7.2": ["nannied"], "-3.1 14.3 3.9": ["guessable"], "-9.6 0.6 4.1": ["toone"], "-0.6 4.8 1.0": ["precommitment"], "13.0 10.2 15.4": ["comparsion"], "4.8 12.2 5.7": ["initialise"], "-1.5 4.0 10.5": ["headnotes"], "-6.0 13.2 5.0": ["symptomology"], "0.9 2.4 7.8": ["aaja"], "4.8 -6.1 10.0": ["dbc"], "17.6 -1.6 20.6": ["cardies"], "10.4 3.3 5.5": ["multiphased"], "1.1 3.8 8.0": ["angio"], "28.4 13.5 44.5": ["nudibranch"], "4.2 4.1 12.1": ["garbas"], "7.8 20.6 6.8": ["unreformable"], "7.2 10.1 15.7": ["govermment"], "-4.6 3.9 8.4": ["khutba"], "13.3 25.2 11.8": ["prevaricators"], "5.4 15.6 12.4": ["kisans"], "1.2 -3.3 -4.3": ["proce"], "-0.8 4.5 7.8": ["prequarterfinals"], "0.6 2.8 1.5": ["cies"], "-2.8 23.9 5.1": ["agendum"], "6.5 28.3 3.8": ["raq"], "-3.3 8.1 22.9": ["feedground"], "0.5 2.8 1.3": ["oxypurinol"], "6.5 9.1 14.3": ["biotinylated"], "4.1 17.6 8.2": ["synaesthetic"], "7.4 4.2 15.1": ["backfills"], "25.3 8.5 -3.1": ["onits"], "3.0 26.3 11.6": ["inescapability"], "5.6 12.7 12.9": ["indenter"], "1.5 0.3 6.9": ["yays"], "2.3 5.7 4.1": ["bronchoscopic"], "3.9 5.0 5.7": ["withtheir"], "11.7 10.2 10.0": ["bespeaking"], "18.7 -9.0 4.3": ["strongwoman"], "7.6 -1.0 18.1": ["yorkshire"], "-0.3 17.1 8.3": ["awfull"], "3.6 17.1 11.7": ["neighboorhood"], "11.4 -4.5 3.7": ["topay"], "5.7 5.7 7.9": ["dimethyltryptamine"], "8.9 8.7 14.3": ["garagey"], "11.0 5.3 9.8": ["commodites"], "5.9 23.5 -0.2": ["engrams"], "17.1 26.1 9.6": ["windborne"], "-0.6 -3.1 10.6": ["offpeak"], "4.0 2.3 8.9": ["nadie"], "9.1 4.0 21.5": ["bouche"], "2.7 1.0 6.3": ["winers"], "4.7 15.0 16.2": ["invigoratingly"], "1.6 6.5 5.0": ["odissi"], "12.0 10.3 12.3": ["joie"], "1.4 5.6 -11.8": ["gurantees"], "-3.6 -2.5 8.3": ["reserva"], "19.0 27.2 12.1": ["mambas"], "19.2 11.1 18.9": ["tacker"], "4.3 25.3 5.4": ["desperateness"], "26.0 -0.1 18.8": ["stiltwalker"], "-4.3 -0.9 3.3": ["headships"], "10.5 17.0 9.1": ["industrializes"], "16.9 18.3 10.6": ["rhomboids"], "-4.2 6.1 -2.5": ["mentionned"], "5.8 0.0 3.9": ["unprocedurally"], "11.8 9.9 16.0": ["dogwalker"], "11.6 11.7 15.1": ["floozie"], "5.6 34.8 4.9": ["wargamers"], "18.7 13.1 17.3": ["lamped"], "-1.3 16.6 6.3": ["narrowminded"], "3.7 5.7 30.1": ["outfished"], "16.0 4.2 12.8": ["tearless"], "6.2 3.2 4.8": ["sourceforge"], "11.8 6.5 19.0": ["hatpins"], "11.1 7.8 4.4": ["limewire"], "12.2 9.3 34.3": ["butterflyfish"], "1.1 9.4 12.1": ["hija"], "0.1 -0.4 13.6": ["tulong"], "3.5 0.3 12.1": ["ultrastructural"], "12.9 14.1 9.4": ["goodism"], "20.5 15.3 20.8": ["midstride"], "7.5 3.4 19.6": ["ferritic"], "4.1 8.1 16.7": ["umping"], "11.9 7.5 25.8": ["salicornia"], "5.0 1.2 7.8": ["kermesse"], "6.8 -2.6 8.2": ["nhw"], "3.8 9.6 5.2": ["sickbeds"], "1.5 26.9 -1.7": ["antagonises"], "-8.7 3.2 2.9": ["missiology"], "9.2 2.1 2.3": ["hosptials"], "10.6 6.5 23.3": ["riz"], "-2.8 8.1 -2.3": ["defalcations"], "9.3 16.4 19.0": ["dihedral"], "17.0 7.3 13.9": ["concertinas"], "11.9 13.8 5.2": ["smarmily"], "4.1 10.5 5.9": ["untyped"], "-0.8 9.9 13.1": ["tocome"], "16.2 7.3 -0.5": ["marketting"], "19.4 14.5 17.4": ["paintbox"], "0.5 6.7 10.2": ["prilocaine"], "5.3 7.4 11.2": ["peru"], "8.5 10.6 16.0": ["hydrator"], "20.5 17.6 21.9": ["openmouthed"], "12.8 13.8 -6.0": ["stiffled"], "10.1 20.8 6.2": ["connotative"], "6.4 6.9 8.1": ["nickled"], "8.2 -3.8 8.9": ["polyacrylamide"], "-7.1 8.3 12.7": ["intersexuality"], "7.7 15.1 11.4": ["favourties"], "-0.2 4.4 14.1": ["walis"], "3.2 12.1 16.3": ["waay"], "12.5 7.7 11.5": ["splined"], "5.0 17.2 9.7": ["repeatably"], "4.1 7.8 16.5": ["feldspathic"], "17.2 11.4 13.1": ["optimus"], "-0.5 11.3 0.1": ["cardiotoxic"], "6.8 -0.8 11.8": ["liniments"], "3.8 10.3 14.3": ["avascular"], "9.7 10.3 14.3": ["luciferin"], "15.7 12.7 11.9": ["vav"], "3.1 9.4 12.3": ["talkbox"], "3.3 -1.3 13.1": ["kap"], "-4.4 7.6 5.2": ["imformation"], "-5.0 2.6 6.2": ["aws"], "10.1 0.2 15.5": ["weber"], "14.3 15.2 16.0": ["colonises"], "15.3 21.4 14.4": ["nanites"], "16.7 8.6 13.8": ["thrilla"], "-3.3 20.1 -2.8": ["hawaldar"], "-8.5 7.1 1.7": ["disenrollments"], "-3.5 4.5 17.5": ["wirebond"], "7.5 13.8 6.8": ["johnnies"], "5.3 9.2 6.1": ["incorrigibles"], "-1.0 9.6 14.6": ["megabase"], "24.1 16.6 16.6": ["matryoshka"], "7.4 1.4 9.2": ["hyperimmune"], "2.3 19.7 12.5": ["epigenetically"], "13.3 14.2 12.7": ["chaddar"], "-5.1 8.3 6.2": ["mikve"], "9.6 -0.7 24.1": ["brite"], "-5.8 -1.6 8.8": ["isd"], "-3.7 8.7 5.2": ["kazi"], "3.1 20.7 5.3": ["naivet"], "10.5 1.9 3.9": ["tzar"], "7.3 7.0 13.7": ["autoclavable"], "7.9 -0.2 13.6": ["copa"], "-9.4 8.0 -2.0": ["notetaker"], "5.4 2.4 9.8": ["saddlers"], "6.5 9.7 5.3": ["clubmaker"], "36.5 30.8 22.7": ["spiderlike"], "6.9 25.4 12.1": ["ungratefully"], "7.3 21.2 14.7": ["vicissitude"], "13.1 0.5 9.2": ["afforable"], "5.6 -6.3 6.0": ["partcipate"], "5.5 11.3 10.4": ["rangier"], "10.5 12.0 40.5": ["cladophora"], "4.0 8.9 -0.9": ["vison"], "23.6 19.6 11.3": ["microbots"], "11.7 14.2 4.7": ["immateriality"], "17.3 17.6 11.4": ["pyscho"], "14.6 6.2 23.3": ["gluhwein"], "4.7 13.6 30.7": ["murgh"], "15.9 3.5 0.4": ["geomechanics"], "12.0 0.7 24.5": ["amarillo"], "4.3 13.1 11.1": ["crossdressers"], "-4.1 13.4 -2.7": ["psychodynamics"], "6.3 7.6 7.5": ["technoparks"], "-1.0 5.2 2.6": ["minicom"], "3.6 5.0 12.3": ["buen"], "8.5 6.2 4.4": ["zoals"], "20.3 -4.0 12.1": ["juicemaker"], "17.0 15.9 21.6": ["clangor"], "-0.6 4.6 16.7": ["kahiko"], "-3.1 -1.7 4.7": ["lyase"], "1.4 13.1 0.2": ["undestand"], "6.3 1.8 31.9": ["baboy"], "10.1 16.7 18.8": ["twitterpated"], "6.3 9.6 15.4": ["razzes"], "12.2 -5.6 11.3": ["lithos"], "9.3 5.1 18.5": ["atour"], "2.3 21.2 12.4": ["siderophores"], "10.7 15.5 21.1": ["jokin"], "14.6 8.6 5.7": ["catwalking"], "12.5 9.7 21.6": ["hansik"], "13.7 6.6 14.4": ["plastinates"], "0.7 2.2 10.3": ["senador"], "13.9 -0.3 1.3": ["servicesand"], "4.8 9.7 9.9": ["texans"], "-3.7 16.6 7.9": ["kinships"], "3.8 2.3 6.9": ["sustainabilty"], "7.5 11.6 11.0": ["philospher"], "9.1 6.1 6.1": ["borescopes"], "3.0 -0.0 11.6": ["morphometric"], "8.0 15.8 21.6": ["hardway"], "2.7 1.8 7.9": ["lortab"], "5.3 11.0 -0.6": ["sicne"], "9.0 -0.1 7.1": ["growning"], "7.3 -4.2 7.1": ["increasein"], "4.1 15.5 15.4": ["earflap"], "2.8 16.9 3.9": ["complacencies"], "-2.8 4.8 6.6": ["audiography"], "7.5 7.7 18.3": ["jenkins"], "4.5 25.7 3.3": ["strifes"], "11.3 16.3 7.9": ["flatstick"], "0.2 2.3 7.4": ["coevals"], "-2.1 9.2 19.9": ["creeking"], "5.0 10.9 5.2": ["neocortical"], "18.4 -0.1 19.3": ["arabian"], "3.9 11.2 23.1": ["polyculture"], "15.0 16.5 13.2": ["elavil"], "-4.1 9.3 1.0": ["fedup"], "16.1 7.9 6.9": ["nascence"], "17.6 5.5 31.6": ["manju"], "6.3 9.7 5.3": ["liablity"], "2.2 -5.9 8.6": ["comissioners"], "16.6 5.8 4.3": ["furors"], "2.0 3.3 6.9": ["worktime"], "17.6 4.2 16.9": ["upo"], "-2.8 6.8 11.3": ["subjectto"], "10.2 -0.1 3.4": ["welshed"], "14.6 16.7 29.2": ["bodysurf"], "-0.8 13.7 10.8": ["ladki"], "-2.5 0.7 9.0": ["bacteriuria"], "6.6 14.7 13.9": ["possesing"], "5.8 12.6 9.3": ["horizontality", "urbanely"], "-3.0 2.4 14.5": ["nonunions"], "5.6 13.3 10.2": ["iobi"], "-6.2 8.0 2.9": ["befriender"], "-0.1 1.3 6.5": ["sclerosing"], "12.4 0.3 17.7": ["rouched"], "13.8 21.0 9.3": ["havok"], "-1.1 1.7 1.9": ["consanguineous"], "-5.8 -4.1 11.7": ["multigrade"], "9.1 4.9 10.7": ["rostrums"], "12.4 9.7 -2.9": ["nanotechnologist"], "8.0 17.5 12.1": ["thuringiensis"], "21.7 13.7 8.3": ["supremecy"], "16.5 13.5 38.5": ["megamouth"], "8.1 9.2 11.7": ["seu"], "-5.7 8.0 11.3": ["soleus"], "12.4 9.0 22.1": ["snappin"], "5.9 -1.4 7.5": ["meu"], "17.8 28.2 21.6": ["halberds"], "6.7 6.6 7.4": ["nippier"], "-1.8 7.0 11.8": ["brenda"], "11.9 5.5 7.9": ["jeux"], "9.0 -1.8 11.0": ["kalamkari"], "-3.2 -0.9 4.5": ["replead"], "-0.5 12.0 16.7": ["andrews"], "24.6 10.2 6.4": ["carmarker"], "6.6 20.0 1.5": ["serbia"], "5.7 9.7 19.8": ["wheelwells"], "-3.7 4.0 9.7": ["subtherapeutic"], "10.2 19.7 14.2": ["dipshits"], "-7.2 3.8 3.1": ["chazzan"], "7.3 9.8 5.1": ["retranslation"], "0.5 1.7 1.7": ["iray"], "-1.1 24.9 1.7": ["unattributable"], "-4.5 5.7 16.6": ["masterpoints"], "1.9 3.1 35.9": ["headboat"], "-0.3 12.3 4.8": ["intraductal"], "1.5 5.3 3.4": ["arnona"], "12.7 7.7 3.5": ["megaconference"], "9.6 -0.3 8.0": ["softback"], "-0.8 4.5 6.2": ["allophone"], "9.1 15.3 17.9": ["dobbers"], "11.5 31.2 6.3": ["nightvision"], "-0.0 25.6 13.2": ["unwarned"], "6.2 12.2 13.9": ["moses"], "3.3 6.6 7.4": ["vict"], "5.6 15.9 30.0": ["wireworms"], "-1.6 -0.3 3.2": ["avalible"], "11.1 -3.4 7.2": ["memoribilia"], "-0.3 34.6 3.1": ["deconfliction"], "25.3 19.0 12.9": ["fembots"], "7.2 9.0 8.3": ["fingertipped"], "13.9 10.4 8.0": ["trippiest"], "-0.4 2.1 8.0": ["hemm"], "-2.4 13.7 4.2": ["coordinately"], "13.2 10.0 15.1": ["babelicious"], "4.0 4.9 24.1": ["ecotours"], "-0.9 18.9 -3.4": ["edifies"], "6.9 8.6 28.1": ["versicolor"], "5.1 2.9 9.3": ["scarlett"], "-0.1 12.3 12.4": ["syntaxes"], "15.3 19.1 18.2": ["benignity"], "-0.1 5.0 -2.6": ["reconverting"], "18.1 7.0 20.8": ["etiolated"], "6.8 4.0 19.2": ["nonseasonal"], "-0.1 2.1 6.3": ["pretesting"], "8.8 12.0 17.9": ["winsomeness"], "4.0 12.2 4.4": ["slushbox"], "1.2 -0.6 13.1": ["erba"], "6.9 -3.4 11.8": ["nue"], "-1.8 9.7 12.5": ["nfp"], "7.3 5.2 -3.0": ["noviny"], "5.9 4.3 6.0": ["cystoscope"], "8.8 0.8 3.5": ["radiobiology"], "12.4 15.5 10.1": ["chessboxing"], "3.3 2.4 14.0": ["sourer"], "12.0 10.7 9.8": ["mutex"], "1.2 5.9 4.9": ["rebailed"], "19.9 -5.5 1.0": ["procent"], "10.5 17.2 5.7": ["seriatim"], "13.6 4.5 26.8": ["rodizio"], "-3.9 14.7 7.7": ["regi"], "5.5 0.6 7.3": ["downlighting"], "11.2 13.2 13.3": ["comingle"], "12.5 11.9 8.2": ["directionals"], "5.2 6.0 6.8": ["equitising"], "6.6 10.9 34.7": ["larb"], "4.2 19.6 6.9": ["compartmentalising"], "3.8 0.3 3.3": ["pik"], "6.6 3.0 7.1": ["grandchildrens"], "9.0 4.9 39.4": ["marionberry"], "6.9 5.4 1.9": ["einfach"], "-4.0 22.8 4.2": ["laborites"], "17.6 11.5 15.9": ["poppets"], "11.5 -0.4 27.3": ["cusine"], "14.8 13.8 23.1": ["bowerbird"], "18.6 10.1 26.1": ["peckers"], "15.2 5.8 3.5": ["intermeshing"], "16.4 8.4 30.8": ["tuiles"], "-8.1 2.6 2.0": ["palivizumab"], "3.7 3.3 0.6": ["acronymed"], "8.5 10.0 13.0": ["hiz"], "4.1 15.1 12.4": ["royalsreview"], "8.9 11.7 8.6": ["shennanigans"], "14.4 -0.2 36.1": ["malasadas"], "7.2 6.5 -3.9": ["injuncted"], "7.9 14.9 6.8": ["bafana"], "-0.3 9.0 6.3": ["upconverters"], "9.0 16.9 9.2": ["bandoleer"], "2.3 17.4 17.9": ["moneylines"], "2.4 -1.1 15.9": ["soapmaking"], "4.5 14.9 6.0": ["generaly"], "3.3 3.2 4.2": ["somonis"], "-4.0 17.8 1.4": ["incompetencies"], "-0.4 10.8 5.6": ["economization"], "5.7 -1.1 13.3": ["kuan"], "9.9 5.5 10.9": ["tuggers"], "-0.4 16.7 -1.3": ["inconsistence"], "24.4 13.1 13.0": ["plutonomy"], "17.8 6.8 11.4": ["bux"], "16.1 18.3 20.6": ["shitshow"], "6.6 9.2 34.6": ["cinnamony"], "9.5 -0.3 7.0": ["coversion"], "-0.9 0.3 1.9": ["propanol"], "6.4 8.3 7.8": ["favourtism"], "5.3 9.4 9.7": ["paladares"], "10.2 -2.7 8.4": ["sleuthed"], "-0.7 -2.5 4.9": ["clubnight"], "4.6 -1.8 4.8": ["oxygenators"], "5.5 8.7 11.1": ["manish"], "5.5 13.0 8.2": ["pratt"], "-0.8 12.3 1.5": ["extinguishments"], "8.4 -0.2 5.0": ["warrenty"], "-5.4 14.1 15.6": ["perverseness"], "5.7 5.9 6.7": ["intitiatives"], "12.5 15.6 19.8": ["kiddish"], "1.9 3.1 11.8": ["rackspace"], "7.4 6.6 12.7": ["stretchiness"], "1.4 13.6 4.2": ["wohl"], "-4.9 16.9 14.4": ["federalisation"], "5.8 22.8 7.9": ["redivision"], "4.0 4.1 3.8": ["hryvnyas"], "12.9 -0.3 22.8": ["silverplate"], "10.2 8.3 31.3": ["blackcap"], "13.5 5.2 12.9": ["pagentry"], "16.7 7.6 22.4": ["mushes"], "-1.1 5.5 2.3": ["chemoprotectant"], "-5.7 14.5 6.2": ["collectivistic"], "-8.2 5.5 5.3": ["edi"], "-1.3 22.7 -1.1": ["fuzing"], "-0.0 3.2 17.5": ["kira"], "7.4 1.9 19.7": ["pipelaying"], "2.0 6.3 -0.6": ["thefield"], "1.2 2.6 -3.2": ["respons"], "2.9 4.9 28.3": ["gaharu"], "14.8 12.6 3.3": ["defeaning"], "8.5 24.0 0.2": ["attac"], "12.6 9.8 22.5": ["saluki"], "-1.3 -3.2 8.1": ["workship"], "0.7 9.4 16.4": ["homegirls"], "12.3 4.7 14.6": ["squeegeeing"], "2.2 9.3 10.9": ["relocalization"], "11.9 0.2 7.4": ["lpg"], "8.6 9.1 7.6": ["timesavers"], "10.1 14.8 9.8": ["irreproducible"], "13.3 2.8 10.1": ["slipcovered"], "10.2 -5.3 1.3": ["cwmni"], "2.3 4.7 14.8": ["laging"], "2.0 6.9 10.8": ["smtp"], "3.6 13.9 9.6": ["poilce"], "9.8 19.7 12.2": ["irrecoverably"], "6.1 6.8 11.7": ["bellhousing"], "9.9 12.5 10.4": ["finland"], "2.7 19.7 14.8": ["operands"], "7.3 12.3 12.2": ["interactome"], "5.0 1.5 6.8": ["nuestros"], "12.4 14.9 18.0": ["cowboyed"], "-1.1 3.5 2.8": ["aryl"], "3.8 2.0 3.4": ["rwhp"], "12.2 8.2 12.2": ["unreleasable"], "-0.4 4.5 11.7": ["comunidades"], "-3.7 0.2 4.5": ["cocounsel"], "-1.9 8.0 -1.5": ["uninvite"], "-0.1 1.8 -3.0": ["unionlearn"], "9.6 10.6 7.7": ["metrically"], "10.1 9.6 14.3": ["dhak"], "6.0 10.0 6.4": ["scatalogical"], "-4.8 6.4 17.6": ["jel"], "-1.8 3.9 4.6": ["louisville"], "17.9 3.9 12.4": ["supercute"], "14.0 13.3 10.7": ["falteringly"], "12.6 14.9 13.2": ["monkeyshines"], "-5.6 4.9 6.1": ["qanun"], "-3.0 4.6 1.2": ["ofbusiness"], "13.9 3.4 25.7": ["glogg"], "-1.4 -7.6 2.6": ["aspenhome"], "0.0 4.0 5.7": ["hotshoes"], "3.9 -1.1 2.4": ["insidethegames"], "14.1 16.4 18.4": ["biotch"], "9.1 9.3 8.0": ["noncumulative"], "1.9 18.1 2.8": ["humilated"], "-0.6 4.3 -3.5": ["conceptional"], "8.1 -0.6 2.0": ["hightlight"], "16.8 5.6 0.1": ["defrauders"], "17.2 6.2 15.3": ["agritainment"], "8.2 5.1 14.7": ["becak"], "6.4 3.9 2.3": ["spunlace"], "-9.5 12.2 9.3": ["recontact"], "-5.8 9.5 7.8": ["itemizers"], "17.7 5.5 15.5": ["scrawnier"], "5.8 1.5 19.2": ["supperclub"], "7.7 9.0 33.9": ["verjuice"], "10.3 20.0 8.3": ["bulletholes"], "11.8 24.5 11.1": ["ungraspable"], "13.7 5.6 14.4": ["freebase"], "4.2 6.3 16.7": ["mammalogy"], "15.8 6.2 34.3": ["dilled"], "0.0 13.5 12.0": ["agame"], "5.2 4.8 14.3": ["quinn"], "18.1 -8.0 11.1": ["februari"], "9.3 7.4 6.2": ["walas"], "2.9 5.6 6.0": ["retinitis"], "2.2 4.0 9.7": ["tetri"], "4.2 18.0 26.6": ["treif"], "3.6 10.7 8.6": ["elminate"], "-2.9 -8.5 4.6": ["ods"], "13.8 24.2 20.5": ["housetop"], "2.4 22.8 8.9": ["ambivalences"], "16.2 14.0 6.6": ["corpo"], "6.7 6.3 12.8": ["exfoliators"], "-6.8 7.1 13.3": ["nonswimmers"], "-7.3 2.3 -0.3": ["repsonded"], "4.7 10.7 3.7": ["multiwavelength"], "20.7 9.7 52.9": ["crays"], "0.5 -3.7 8.6": ["tured"], "4.7 33.7 5.5": ["combattants"], "12.3 13.7 4.6": ["timeclock"], "7.8 10.6 11.1": ["flowerings"], "4.6 13.7 2.1": ["likelyto"], "3.5 34.2 8.5": ["fitnah"], "9.6 18.6 16.2": ["imperturbably"], "21.0 14.0 29.7": ["cheeping"], "-5.0 4.2 -2.1": ["glucuronide"], "7.9 7.2 4.4": ["enterprisingly"], "5.3 12.7 6.5": ["appositely"], "4.8 23.4 4.7": ["groud"], "20.5 -4.1 34.1": ["pierogie"], "5.0 13.1 9.5": ["nonspecialist"], "13.3 16.2 12.8": ["spendathon"], "7.3 20.4 15.7": ["advection"], "12.9 28.3 13.7": ["demoniac"], "9.2 14.2 13.4": ["skeeved"], "5.2 1.7 2.3": ["interne"], "10.1 2.0 -4.0": ["aformer"], "24.0 12.4 14.4": ["enon"], "-11.1 6.0 1.3": ["uth"], "5.2 3.6 8.5": ["visto"], "2.3 14.5 10.8": ["saccades"], "12.5 20.2 11.8": ["trekkie"], "8.8 8.9 26.1": ["calorically"], "2.5 14.7 9.2": ["superpositions"], "10.1 6.2 -1.0": ["reimporting"], "12.6 -1.3 11.4": ["underrecoveries"], "8.6 7.1 45.2": ["wrasses"], "11.4 8.9 7.2": ["teendom"], "10.7 10.9 15.2": ["ethereality"], "-5.7 15.6 8.5": ["anwer"], "14.2 16.9 17.5": ["dougie"], "-1.8 5.0 2.6": ["diminshed"], "-0.1 1.8 6.5": ["itmes"], "8.4 5.7 4.8": ["whodunnits"], "5.8 6.8 11.4": ["redrill"], "-6.0 2.3 0.9": ["evalution"], "11.4 8.9 -1.7": ["beused"], "-5.2 -0.8 4.0": ["briakinumab"], "5.8 8.9 6.6": ["alkene"], "-1.4 -2.9 16.6": ["yardwaste"], "16.2 18.1 23.8": ["uneatable"], "19.6 22.8 21.1": ["sunward"], "6.6 5.9 6.2": ["redistributable"], "9.4 19.2 21.8": ["panicle"], "3.2 6.5 17.9": ["angelonia"], "-8.1 7.9 5.7": ["idem"], "3.6 4.9 5.8": ["meda"], "5.0 13.4 5.8": ["cleansheets"], "3.7 7.3 4.3": ["panchayati"], "-5.1 9.2 -1.7": ["invesigation"], "0.6 -3.8 6.8": ["lls"], "14.2 -0.3 5.1": ["carryalls"], "-6.4 2.8 7.0": ["parapros"], "12.8 8.8 17.5": ["crossarms"], "8.2 10.9 13.0": ["dramtically"], "2.7 6.4 9.3": ["miscategorized"], "4.4 2.0 23.6": ["sawtimber"], "3.9 11.1 16.7": ["tidally"], "-0.9 7.6 9.1": ["hilar"], "2.7 1.0 1.2": ["entreprenuership"], "12.9 0.6 18.2": ["staling"], "-2.1 5.8 9.7": ["malloc"], "2.2 18.7 11.4": ["idenity"], "-10.0 1.6 12.9": ["biennia"], "5.5 15.0 4.7": ["tsuris"], "-3.1 12.1 -0.5": ["disapppointed"], "9.1 12.9 15.9": ["antivenoms"], "-6.1 3.6 2.1": ["mobilehome"], "18.7 7.2 26.3": ["jellylike"], "0.2 25.8 4.5": ["currupt"], "10.2 32.1 3.7": ["hoselines"], "12.5 6.5 29.1": ["currach"], "14.1 25.3 14.3": ["garroting"], "3.6 10.2 13.4": ["chace"], "8.9 5.6 13.9": ["sani"], "19.9 25.3 26.2": ["annelids"], "14.4 14.5 11.2": ["lechers"], "1.5 6.5 14.6": ["excerise"], "-1.7 4.2 0.3": ["encuentro"], "4.8 9.9 13.0": ["dwalters"], "5.4 15.8 9.5": ["overreporting"], "8.2 0.4 14.9": ["toma"], "7.2 19.1 11.7": ["discardable"], "1.1 4.2 4.8": ["disapprovals"], "7.1 9.1 -0.4": ["radiocommunications"], "6.6 7.4 19.2": ["chaud"], "2.8 0.2 1.6": ["withi"], "-7.1 11.9 14.1": ["kinetochores"], "10.3 4.6 4.7": ["thiomersal"], "6.0 3.1 13.1": ["nonpharmacy"], "19.7 5.5 9.2": ["rainsoaked"], "-1.0 1.9 7.6": ["lem"], "8.1 15.3 -0.5": ["undoubtly"], "12.2 18.5 14.8": ["gluttonously"], "10.3 3.0 0.6": ["songtress"], "3.0 1.0 11.9": ["outriding"], "27.1 10.2 32.2": ["tetras"], "9.7 4.6 -3.3": ["biturbo"], "9.7 2.1 10.5": ["coextruded"], "17.1 11.2 11.0": ["shoutin"], "-0.2 5.2 16.6": ["cinsault"], "0.5 4.7 8.5": ["consequat"], "1.7 13.8 18.0": ["yt"], "13.2 23.7 27.1": ["fletching"], "0.4 5.0 11.9": ["curr"], "3.9 1.9 6.9": ["furbished"], "13.8 6.3 9.8": ["thermoacoustic"], "11.4 21.3 12.8": ["ludus"], "8.4 4.3 7.1": ["mientras"], "4.6 0.7 5.8": ["unsegregated"], "1.0 -1.0 13.8": ["tively"], "6.9 6.9 21.6": ["alala"], "-5.9 2.4 -0.2": ["recodification"], "1.8 1.5 8.4": ["chuk"], "-3.5 13.6 3.1": ["druggable"], "-5.1 9.3 8.0": ["critieria"], "5.1 24.2 3.9": ["credulousness"], "6.6 8.1 4.0": ["outcoming"], "3.2 1.8 2.9": ["videomakers"], "7.2 -0.7 14.4": ["coreboard"], "16.4 5.0 5.5": ["neverthless"], "2.4 7.2 10.7": ["dys"], "6.9 31.5 19.7": ["gank"], "12.2 7.6 26.3": ["kadai"], "4.8 7.1 7.0": ["hyperlens"], "11.4 27.1 10.3": ["mainlands"], "-2.9 10.6 -9.9": ["inacceptable"], "13.2 6.1 18.0": ["plinks"], "10.7 14.8 16.4": ["chimenea"], "18.3 15.1 19.5": ["mountainscape"], "2.2 31.6 11.1": ["ganking"], "7.9 -3.8 3.0": ["logiciel"], "11.1 4.1 13.7": ["reshipping"], "1.9 1.5 17.4": ["oneand"], "12.7 14.1 8.0": ["ditziness"], "2.9 2.4 12.6": ["liscence"], "20.0 2.1 11.5": ["pumpjacks"], "1.1 16.7 16.8": ["cofilin"], "6.8 3.3 6.0": ["perfectors"], "6.3 11.8 12.2": ["toungue"], "11.7 -0.6 16.8": ["ukes"], "-1.7 6.3 14.7": ["myelopathy"], "4.6 -5.8 8.4": ["filles"], "12.4 9.4 4.9": ["electroencephalograph"], "-3.4 3.6 10.2": ["prepregnancy"], "6.0 3.4 15.6": ["ecolabels"], "3.2 0.8 11.2": ["urolithiasis"], "1.9 -0.9 1.0": ["carbamate"], "-6.4 5.6 14.4": ["bais"], "7.6 9.3 5.3": ["bestbuy"], "-2.6 7.6 2.6": ["zvelo"], "14.9 12.3 9.8": ["paintjobs"], "7.0 31.9 7.3": ["assasins"], "8.1 4.3 11.1": ["diferentes"], "-0.2 -0.8 6.0": ["rehabing"], "9.0 -5.0 -6.6": ["relesed"], "-0.6 6.9 8.7": ["jocked"], "10.7 3.5 14.5": ["nri"], "13.9 1.9 39.5": ["legered"], "9.9 1.8 49.8": ["cusk"], "17.5 5.1 5.6": ["basketbrawl"], "5.6 6.2 31.8": ["guajillo"], "6.2 11.7 9.9": ["crystallites"], "14.6 27.8 6.9": ["homicidally"], "2.7 7.7 11.0": ["aisi"], "13.3 0.5 6.1": ["wirth"], "9.9 2.1 5.4": ["prochain"], "10.9 24.6 11.5": ["mischance"], "1.9 5.5 11.2": ["munity"], "12.3 9.8 22.4": ["ponderosas"], "7.9 24.3 16.9": ["nutsy"], "14.4 5.2 19.0": ["unknotted"], "10.9 28.2 14.5": ["needler"], "4.7 6.8 19.1": ["ashwagandha"], "11.9 12.4 31.0": ["stonecrop"], "9.4 7.9 0.7": ["shopflick"], "3.0 9.7 6.4": ["simcards"], "30.9 39.1 14.0": ["autobots"], "1.1 13.8 14.4": ["overtighten"], "1.3 9.0 1.5": ["spox"], "-0.3 0.5 5.3": ["tudents"], "2.9 13.3 -0.5": ["magnetoresistance"], "16.2 7.4 16.8": ["pelmet"], "2.1 4.3 6.0": ["oftwo"], "16.7 26.0 18.8": ["toofastforyou"], "2.4 5.8 3.9": ["mortgagers"], "6.9 1.7 35.5": ["mostarda"], "-2.3 7.5 0.6": ["representativity"], "14.9 7.0 54.9": ["saury"], "14.6 18.3 5.4": ["darknets"], "7.2 0.1 -2.8": ["disppointed"], "16.9 15.8 16.7": ["gurn"], "8.0 17.1 23.2": ["tranquillise"], "16.4 24.2 31.3": ["predacious"], "7.9 2.1 9.9": ["sheerness"], "-1.0 7.0 7.1": ["calypsoes"], "6.9 10.8 4.2": ["neede"], "-3.2 4.8 3.5": ["dysphasia"], "2.8 11.6 14.1": ["adverbial"], "19.2 21.2 15.1": ["gouts"], "-2.8 22.6 11.3": ["dhikr"], "4.3 15.0 16.0": ["bisping"], "1.4 13.9 -1.7": ["antifeminist"], "4.8 16.5 6.3": ["ebertchicago"], "-0.6 16.9 10.4": ["unlogged"], "6.7 6.7 8.6": ["enteprise"], "2.9 9.6 2.1": ["ethnographies"], "8.7 -1.3 14.0": ["naf"], "19.9 14.2 6.5": ["sceen"], "20.1 13.1 14.9": ["papercut"], "-2.9 11.7 10.7": ["gham"], "2.6 11.2 6.9": ["policier"], "6.6 10.7 2.2": ["bastardise"], "4.8 18.8 18.6": ["nontarget"], "10.7 1.4 16.4": ["potpourris"], "13.1 1.8 10.0": ["fashiony"], "-3.5 4.8 8.1": ["geodemographic"], "8.6 3.0 8.1": ["weg"], "11.8 18.2 5.6": ["firebomber"], "17.2 10.9 22.0": ["flakiest"], "0.9 7.2 11.3": ["returnman"], "3.5 6.3 6.8": ["agan"], "28.0 1.9 7.7": ["nickelodeons"], "6.9 21.1 15.4": ["rappellers"], "14.2 12.2 19.6": ["tuchus"], "0.4 24.6 11.5": ["hyperaware"], "20.6 -4.7 9.8": ["sectorwide"], "20.8 18.8 18.7": ["outspread"], "11.7 4.1 11.9": ["trhough"], "-6.0 8.0 13.5": ["classtime"], "16.5 6.9 13.4": ["shipbreakers"], "5.5 32.5 3.3": ["delegitimising"], "2.8 18.7 30.3": ["bateaux"], "3.8 3.9 12.9": ["planta"], "6.5 1.6 0.9": ["latests"], "7.0 7.3 -1.4": ["turboshaft"], "2.6 10.9 11.9": ["virgo"], "10.8 5.4 6.6": ["underinvest"], "9.8 -3.2 4.7": ["interpack"], "8.6 -0.4 5.3": ["mab"], "2.4 10.7 5.9": ["constituants"], "4.8 16.1 2.7": ["yeards"], "-6.2 5.9 5.4": ["paricalcitol"], "15.1 15.0 8.2": ["centimer"], "-2.3 8.0 10.2": ["actuallly"], "3.5 1.2 12.7": ["bawat"], "6.5 26.1 5.8": ["ethnicism"], "7.9 7.3 8.6": ["cyanides"], "8.9 8.1 9.4": ["odt"], "3.0 0.9 1.5": ["voivodship"], "2.9 19.8 11.8": ["mythologising"], "1.0 11.3 15.0": ["hemolytic"], "12.2 7.6 9.7": ["fulldome"], "11.5 8.9 0.2": ["liste"], "25.7 9.2 10.8": ["oilwell"], "-10.1 4.3 -5.8": ["novelized"], "4.8 -5.0 -6.2": ["inagurated"], "16.0 -0.3 13.1": ["busch"], "12.7 23.2 10.0": ["alethiometer"], "-2.0 5.4 3.8": ["sanatoria"], "6.7 3.4 9.9": ["dail"], "15.3 -1.8 12.1": ["busks"], "19.9 2.9 20.3": ["chewin"], "11.4 16.1 6.2": ["flaccidity"], "6.8 3.6 2.2": ["transdermally"], "17.0 26.9 12.3": ["timebombs"], "9.8 25.5 6.1": ["vindicator"], "4.9 4.3 2.7": ["takebacks"], "3.5 17.1 24.6": ["cayes"], "-1.2 16.9 6.4": ["undemarcated"], "11.1 12.1 20.7": ["coxes"], "-1.2 11.5 2.8": ["fard"], "13.4 8.1 4.3": ["reskin"], "3.4 31.2 14.8": ["solitariness"], "1.7 -2.2 1.8": ["integratable"], "3.4 4.9 2.3": ["dominee"], "22.9 9.6 21.9": ["beanpoles"], "3.8 3.6 10.6": ["unpin"], "-1.6 -5.2 4.7": ["theevent"], "8.2 3.6 13.4": ["yoni"], "3.1 -5.3 2.5": ["biolitec"], "1.1 4.9 2.3": ["isue"], "5.0 7.7 1.7": ["annunciator"], "7.2 23.3 5.3": ["loathesome"], "1.2 10.5 11.3": ["carious"], "15.3 19.4 17.6": ["hearties"], "16.5 0.8 3.6": ["opticals"], "5.3 1.8 6.4": ["pennystocks"], "11.5 -6.2 -3.9": ["excecutive"], "16.1 20.2 9.2": ["plastique"], "10.8 13.1 22.4": ["atmos"], "-7.7 0.3 4.2": ["prebates"], "7.7 0.4 17.0": ["tico"], "8.3 12.3 4.5": ["helistop"], "3.6 21.1 10.0": ["diarchy"], "16.5 9.0 5.4": ["stshank"], "7.8 8.9 7.1": ["biogases"], "7.8 -1.2 14.5": ["testa"], "5.6 11.2 -0.6": ["seminfinals"], "5.8 8.2 10.1": ["aeromagnetics"], "6.8 20.6 9.3": ["unempowered"], "8.8 10.4 7.5": ["bioregional"], "-3.4 2.8 14.2": ["viticulturalist"], "10.1 3.3 12.0": ["consols"], "15.6 11.3 17.4": ["mountie"], "12.7 10.7 15.1": ["anyhoo"], "9.3 18.6 19.3": ["eusociality"], "-1.2 10.8 -4.0": ["emplaning"], "13.2 5.3 11.3": ["hipping"], "2.6 6.5 4.4": ["lithotripter"], "14.6 9.1 10.2": ["palmists"], "2.0 8.9 23.4": ["kaa"], "4.8 11.0 9.5": ["brb"], "8.3 10.6 14.7": ["anthro"], "-1.2 4.7 12.7": ["xen"], "9.4 24.8 3.6": ["hyperviolent"], "-1.3 11.8 16.4": ["chemotactic"], "10.5 6.9 18.3": ["fullish"], "1.3 8.0 11.9": ["foregut"], "16.7 -1.2 4.1": ["profitmaking"], "4.5 10.0 23.0": ["michelada"], "0.6 0.8 9.4": ["nonrestrictive"], "11.1 15.7 9.1": ["propably"], "13.0 9.1 12.8": ["flattener"], "13.3 15.2 19.2": ["doms"], "9.6 19.0 25.1": ["goombah"], "1.0 13.3 11.6": ["jeannie"], "3.1 16.4 9.0": ["flukiest"], "5.3 12.6 0.9": ["sideloaded"], "4.9 -4.0 3.5": ["financialresults"], "0.6 19.7 6.8": ["recallers"], "-8.6 3.5 4.5": ["datarates"], "3.4 16.4 12.2": ["sukkot"], "16.9 2.9 5.5": ["andcoming"], "-0.2 15.6 20.6": ["iodised"], "-2.6 9.3 10.2": ["fanposts"], "17.6 -6.2 13.9": ["fleamarket"], "1.6 5.9 7.2": ["kothi"], "3.1 3.6 11.9": ["hydrographers"], "9.4 3.9 5.2": ["postnup"], "-0.6 11.7 2.8": ["negitive"], "-9.3 12.6 3.7": ["quoter"], "11.7 16.5 12.7": ["apon"], "-0.7 12.1 4.9": ["demodulate"], "10.4 15.2 14.1": ["agricultures"], "6.8 5.7 6.3": ["schtum"], "18.2 9.8 9.1": ["kerfuffles"], "6.3 -0.1 4.5": ["unenforcable"], "3.8 3.2 15.1": ["aseptically"], "24.2 4.5 25.1": ["sables"], "11.3 12.6 12.3": ["earloop"], "7.7 8.4 23.2": ["devilled"], "10.3 1.7 17.7": ["basketmakers"], "2.0 0.5 10.0": ["hekk"], "-0.6 12.8 3.6": ["prolifers"], "6.0 13.3 8.9": ["neckbrace"], "-4.8 0.2 15.3": ["subfertile"], "4.8 18.9 -1.1": ["edly"], "1.8 6.8 24.9": ["floras"], "-5.1 -0.8 2.3": ["reincarceration"], "4.4 12.9 4.2": ["unconsitutional"], "-6.5 8.2 -4.8": ["tomaintain"], "26.2 15.4 18.6": ["lilliputian"], "5.4 3.0 1.5": ["britannique"], "1.7 2.0 -2.5": ["pegylation"], "2.7 13.8 7.3": ["heterodimer"], "10.9 6.0 7.1": ["mongst"], "-3.9 12.1 -2.7": ["repsect"], "0.8 1.5 1.8": ["aucune"], "18.2 23.5 4.8": ["doodlebug"], "11.3 4.9 0.6": ["dustless"], "7.7 8.7 8.0": ["omnipage"], "-3.4 6.6 10.3": ["noneducation"], "4.9 9.0 24.7": ["bitterbrush"], "19.5 0.8 9.5": ["industr"], "9.1 7.7 10.0": ["effulgence"], "11.7 9.4 -5.6": ["moble"], "10.0 2.4 9.8": ["artics"], "13.5 4.2 23.5": ["midmountain"], "20.9 3.9 -1.3": ["swashbuckled"], "5.5 4.9 2.2": ["sothat"], "7.3 2.6 23.8": ["kona"], "12.1 9.2 21.1": ["falcarinol"], "13.6 13.6 18.0": ["skidoos"], "10.7 -0.2 22.0": ["tortilleria"], "8.7 7.1 18.0": ["gastrulation"], "25.5 22.7 26.3": ["sharklike"], "2.6 2.6 5.7": ["intrahepatic"], "11.5 9.2 7.0": ["tonsuring"], "16.2 27.9 8.9": ["measureless"], "6.5 17.1 1.4": ["underarmed"], "-1.8 8.5 5.1": ["wisen"], "-0.2 -3.4 23.2": ["thundercars"], "6.2 3.7 15.3": ["roastee"], "8.8 4.4 9.0": ["pseudogene"], "0.1 10.7 14.1": ["superback"], "8.5 24.1 19.1": ["dadgummit"], "-2.4 12.3 13.5": ["zazen"], "15.7 4.9 5.7": ["smartball"], "7.8 12.0 3.5": ["hallo"], "-1.3 25.5 1.4": ["milbloggers"], "10.4 12.1 14.5": ["weldments"], "21.0 17.3 4.3": ["tomblike"], "7.2 1.5 20.2": ["ninos"], "0.7 13.5 19.3": ["vernalization"], "-1.8 9.5 9.3": ["thantri"], "0.6 15.6 2.7": ["misattribution"], "9.6 15.8 7.0": ["typographically"], "1.6 12.6 20.4": ["unko"], "13.9 8.2 28.4": ["tourtiere"], "12.8 -4.0 14.9": ["pulltabs"], "-2.1 9.8 11.0": ["dextrin"], "-4.1 12.2 1.9": ["offen"], "-3.5 27.7 5.9": ["subjectivist"], "15.4 13.1 16.5": ["placemarks"], "3.9 17.9 5.3": ["firends"], "13.2 15.1 37.9": ["warmouth"], "9.8 8.8 10.8": ["naves"], "9.7 15.6 13.7": ["disillusionments"], "1.4 5.1 11.4": ["fela"], "22.7 4.6 13.3": ["makarapas"], "4.4 20.8 4.3": ["chamchas"], "-0.6 6.6 17.2": ["dante"], "2.3 16.3 11.3": ["jenas"], "8.6 7.5 7.1": ["buggier"], "15.3 0.9 7.9": ["museumlike"], "1.8 20.1 3.0": ["coercions"], "4.2 4.1 9.7": ["eter"], "3.6 0.8 6.7": ["ginnery"], "17.3 4.9 17.4": ["candymaking"], "13.6 11.2 12.4": ["goos"], "17.8 8.6 30.7": ["insectarium"], "3.1 19.3 0.4": ["misquotations"], "14.0 9.6 7.7": ["laughless"], "12.8 11.7 16.6": ["maracatu"], "10.3 13.1 20.2": ["sizzurp"], "0.2 1.1 5.3": ["wirebonders"], "-1.4 16.1 1.8": ["promisor"], "14.9 1.7 15.0": ["eightball"], "0.3 -6.5 6.6": ["parcs"], "17.7 1.1 24.4": ["foresty"], "11.8 2.7 16.6": ["vugs"], "-1.7 4.9 6.1": ["theimpact"], "0.0 21.8 3.3": ["unwarrantedly"], "-3.1 0.5 -4.4": ["positio"], "0.3 19.0 10.2": ["yrds"], "13.6 12.0 26.5": ["whippoorwills"], "14.7 23.0 19.2": ["sandhogs"], "-5.4 3.1 0.6": ["kamp"], "6.2 10.5 29.1": ["nonnatives"], "9.0 1.3 32.2": ["capons"], "1.3 12.6 16.6": ["stomatal"], "7.7 16.3 17.1": ["jturbin"], "18.8 3.1 15.6": ["pocketwatch"], "4.6 19.6 2.8": ["intersts"], "4.3 5.0 3.2": ["whichthe"], "3.2 31.0 7.5": ["crossfires"], "14.9 10.1 20.4": ["pyrography"], "3.5 3.6 12.4": ["looseleaf"], "-1.2 21.2 3.0": ["hajji"], "18.0 14.8 14.0": ["gloriousness"], "16.9 15.9 6.8": ["asteroidal"], "7.4 4.6 12.9": ["angiotensinogen"], "8.0 17.0 17.3": ["waviness"], "12.3 7.2 8.3": ["voicetones"], "10.4 0.8 31.3": ["cornish"], "6.1 0.8 9.6": ["lenny"], "-1.6 11.8 6.6": ["adebayor"], "14.6 5.0 10.4": ["negligable"], "2.0 21.4 5.9": ["atrociousness"], "10.0 8.4 -2.3": ["fileservers"], "17.0 13.8 16.1": ["thingee"], "9.1 20.5 13.2": ["amusedly"], "3.2 11.7 14.7": ["kono"], "4.8 8.9 5.1": ["opportuntity"], "-1.1 10.9 4.0": ["fibulas"], "13.1 10.7 4.4": ["schnell"], "13.2 23.8 11.4": ["blackhat"], "15.1 18.6 9.0": ["deathers"], "15.7 7.1 18.6": ["gasing"], "8.0 4.9 21.9": ["akara"], "14.8 -1.2 10.5": ["giftshop"], "6.0 5.1 1.6": ["natl"], "-7.4 6.3 8.2": ["syndromic"], "15.6 11.3 12.9": ["squarest"], "17.5 23.0 13.5": ["microgame"], "6.8 18.4 6.4": ["mediocracy"], "11.8 9.5 2.1": ["fotball"], "11.1 19.4 13.8": ["phantasmal"], "-10.1 2.1 2.6": ["seroconverted"], "5.8 19.2 14.1": ["sasses"], "4.9 17.6 10.3": ["predictively"], "22.8 9.1 4.2": ["tranform"], "0.1 1.5 -12.1": ["spoksman"], "0.5 3.3 14.6": ["hermaphroditism"], "11.3 0.2 14.8": ["moussed"], "11.9 7.8 24.1": ["indicus"], "10.6 17.9 19.9": ["bathyscaphe"], "6.1 2.8 8.5": ["mostess"], "6.3 31.3 8.7": ["extenuate"], "0.6 14.4 20.6": ["muthi"], "6.9 -1.2 11.5": ["kull"], "8.6 27.9 6.0": ["shebab"], "2.3 10.6 12.9": ["trapshooter"], "6.2 9.1 8.4": ["climactically"], "5.6 17.5 7.8": ["midset"], "8.8 8.2 1.0": ["ecb"], "19.6 12.0 26.3": ["alpenglow"], "6.2 21.2 5.1": ["isreal"], "6.5 1.4 7.8": ["heatlh"], "13.3 9.5 11.7": ["manlift"], "8.1 9.0 22.1": ["hepatica"], "10.9 15.1 4.9": ["deutschemark"], "9.8 11.8 16.5": ["homophonic"], "3.4 3.1 16.0": ["orogenic"], "17.4 3.0 20.1": ["spinet"], "2.2 16.1 8.0": ["threnody"], "10.3 10.6 8.3": ["samzenpus"], "7.0 5.1 4.5": ["syncreon"], "2.4 11.7 14.3": ["stacy"], "-0.0 1.9 10.2": ["chimerism"], "-4.8 1.2 6.2": ["filesize"], "10.7 7.7 4.2": ["internatonal"], "5.2 4.5 5.1": ["sultriest"], "2.5 0.6 2.0": ["benzyl"], "-0.1 21.9 9.4": ["supects"], "6.7 4.8 2.2": ["formular"], "5.2 28.7 3.5": ["unknowability"], "17.5 5.7 -1.8": ["phonecards"], "8.9 4.5 20.6": ["siamangs"], "-1.5 11.7 16.0": ["poorhouses"], "-9.0 -6.4 -3.5": ["zadeh"], "7.2 -5.9 9.8": ["rica"], "2.4 10.2 6.8": ["kalyan"], "-2.0 11.3 4.6": ["cld"], "13.4 1.9 -5.1": ["refocussed"], "-1.4 12.0 5.7": ["overpraise"], "-0.0 14.7 6.5": ["terri"], "4.7 12.5 7.2": ["evite"], "-7.1 6.7 3.6": ["confirmands"], "9.5 1.7 15.7": ["juga"], "6.0 14.6 -2.7": ["primeminister"], "-3.5 7.2 5.0": ["deformability"], "-7.5 12.8 11.3": ["variabilities"], "0.3 8.8 6.8": ["ballwork"], "23.2 13.4 18.1": ["tetrahedrons"], "10.1 8.1 8.0": ["rolodexes"], "9.0 2.7 14.6": ["nanosphere"], "0.6 10.2 8.6": ["receptively"], "5.6 30.9 8.1": ["pakistanis"], "15.9 9.4 5.7": ["grandstanded"], "8.7 10.8 9.9": ["chivvying"], "26.2 21.6 14.2": ["duopolistic"], "13.3 33.6 10.0": ["eradicators"], "17.7 11.6 27.8": ["duikers"], "-1.2 3.0 2.6": ["sones"], "1.0 8.4 5.6": ["greatgrandfather"], "3.3 5.3 24.2": ["backfat"], "9.5 23.1 4.0": ["compradors"], "0.3 8.4 3.1": ["radiogenic"], "0.0 5.2 3.7": ["valganciclovir"], "5.1 17.6 17.7": ["overeaten"], "13.7 -0.1 27.4": ["tattie"], "17.2 1.2 19.2": ["steatite"], "-1.2 10.1 3.3": ["commutative"], "10.4 19.6 6.1": ["cauterise"], "8.2 13.3 1.8": ["lossed"], "5.4 -0.4 1.3": ["orphange"], "1.6 4.9 11.2": ["btrfs"], "1.4 5.8 14.6": ["kvell"], "12.6 8.8 20.2": ["tanorexic"], "6.5 -2.8 2.3": ["etidronate"], "4.4 10.8 -3.3": ["reproachable"], "16.3 11.1 35.9": ["rarebit"], "16.3 12.7 11.1": ["bumperstickers"], "-1.5 27.0 7.5": ["tahdia"], "-6.6 12.1 8.4": ["heter"], "-1.9 6.2 5.6": ["raul"], "-2.4 9.3 3.5": ["microbicidal"], "5.5 10.3 5.8": ["concretising"], "0.4 28.0 10.8": ["prevaricates"], "0.3 -3.1 9.1": ["ssi"], "12.8 17.2 14.4": ["loathers"], "6.4 0.6 42.3": ["mingo"], "14.9 17.9 14.7": ["ballbearings"], "-2.9 8.1 1.9": ["linkster"], "-6.5 0.3 -5.9": ["dexamphetamine"], "12.7 9.6 14.8": ["cnbc"], "4.9 18.6 10.1": ["placekick"], "3.2 4.4 42.5": ["vannamei"], "7.5 1.7 12.4": ["aspirator"], "4.2 6.4 1.6": ["memebr"], "15.7 6.0 23.9": ["excelsior"], "12.3 8.9 13.0": ["scotty"], "1.3 5.2 32.6": ["tooths"], "5.6 8.8 10.6": ["witn"], "0.1 20.2 3.5": ["judgmentally"], "2.5 9.3 8.1": ["tracklists"], "23.2 14.0 16.5": ["yawed"], "6.8 13.1 19.1": ["wain"], "3.4 4.9 17.6": ["turbidite"], "13.4 22.2 24.9": ["sextants"], "3.9 3.2 6.9": ["fifith"], "9.8 15.3 14.6": ["sluff"], "6.4 6.5 7.5": ["usless"], "-0.7 2.3 4.9": ["pexiganan"], "10.7 2.3 13.4": ["tuo"], "2.2 -4.1 13.0": ["koz"], "11.1 15.2 3.2": ["schoolboyish"], "15.7 8.7 21.4": ["awls"], "5.4 -0.9 2.1": ["miligrams"], "3.8 8.1 9.2": ["lysed"], "23.2 7.2 3.7": ["jumbojet"], "3.8 1.3 2.6": ["implemenation"], "0.4 10.1 6.8": ["zuhm"], "0.3 10.4 9.2": ["bodaboda"], "2.9 5.7 1.1": ["overcollection"], "4.1 12.5 4.8": ["raho"], "-6.8 10.5 2.3": ["predicative"], "9.7 15.1 7.7": ["burglarizes"], "8.1 7.1 31.0": ["hihi"], "11.1 13.2 9.7": ["swots"], "4.7 24.6 14.9": ["demonologist"], "-1.7 6.3 8.2": ["curcuminoids"], "1.8 18.5 11.1": ["manyatta"], "14.9 8.9 5.7": ["curtaining"], "7.4 16.3 16.6": ["fiducials"], "4.0 -3.8 29.4": ["diem"], "3.3 20.0 5.8": ["dutifulness"], "4.6 3.8 14.2": ["sulu"], "7.4 9.7 2.4": ["topseeded"], "2.9 -6.9 -7.8": ["apointed"], "11.3 3.3 1.2": ["biometrical"], "4.6 12.0 5.7": ["flashdrive"], "13.2 19.4 10.5": ["bureaucratism"], "3.3 6.6 9.1": ["cannulae"], "1.2 10.0 4.9": ["accountabilty"], "15.6 0.2 6.4": ["posterboards"], "25.7 15.9 31.2": ["carapaces"], "1.1 -3.1 1.6": ["carnet"], "8.8 16.4 14.3": ["phwoar"], "4.2 13.2 3.8": ["immiscible"], "-4.8 7.2 -0.7": ["priories"], "8.9 -10.0 22.6": ["bau"], "-9.1 8.8 4.3": ["bioaerosols"], "7.1 3.5 10.4": ["hela"], "8.7 14.7 10.5": ["unhide"], "-2.7 6.8 11.4": ["saidthey"], "13.2 1.8 5.3": ["agarbattis"], "-0.2 12.8 9.7": ["noncommittally"], "10.3 7.0 11.8": ["ciudad"], "24.0 12.7 19.3": ["strumpets"], "7.3 11.9 13.1": ["freerider"], "15.4 12.6 16.5": ["dousings"], "12.7 12.9 11.6": ["masquerader"], "9.9 2.0 6.3": ["fior"], "0.1 21.4 11.6": ["retrogress"], "3.0 6.3 12.2": ["amatuers"], "2.9 7.4 11.6": ["kuchh"], "21.7 21.4 31.0": ["myna"], "8.3 7.0 10.7": ["monozukuri"], "16.2 10.4 22.2": ["dibbly"], "5.0 11.6 -3.5": ["whther"], "-8.7 -0.3 1.9": ["prucalopride"], "8.2 11.2 19.7": ["timmy"], "16.6 8.4 9.2": ["spookfest"], "14.1 10.5 14.1": ["kidults"], "9.8 -0.6 6.1": ["barr"], "9.2 -2.7 15.2": ["strawbale"], "7.0 8.7 9.6": ["missable"], "9.3 2.8 2.0": ["fims"], "8.4 3.8 14.7": ["gite"], "4.1 10.2 7.5": ["circuitries"], "3.9 -3.7 -2.4": ["videocasting"], "2.4 4.6 7.1": ["fissuring"], "7.1 8.6 7.5": ["stablisation"], "18.5 8.7 19.7": ["sumptious"], "15.4 5.7 9.4": ["semisub"], "11.2 16.0 6.8": ["obselete"], "16.2 9.3 24.9": ["howdah"], "9.6 27.2 18.7": ["commensals"], "-8.1 1.3 3.8": ["dramaturges"], "6.8 0.8 12.3": ["domingo"], "9.6 6.7 16.8": ["pudginess"], "0.6 10.7 12.4": ["tetramers"], "3.8 10.9 7.0": ["goodby"], "-6.0 -2.4 14.8": ["qc"], "13.7 8.3 14.6": ["promissing"], "25.7 8.2 30.5": ["croquembouche"], "2.7 10.1 1.6": ["gatemen"], "-2.1 7.8 10.1": ["wellfare"], "24.8 9.7 16.3": ["shinola"], "14.6 8.8 14.6": ["skiis"], "4.8 11.0 11.1": ["surtout"], "-3.8 2.3 9.3": ["pushouts"], "5.4 12.2 14.7": ["spall"], "33.2 2.4 15.4": ["supersizes"], "-2.6 9.9 -2.8": ["thethe"], "6.0 10.7 16.6": ["sickroom"], "11.9 4.0 43.4": ["enoki"], "-8.8 18.3 -3.0": ["hassidim"], "3.6 28.4 1.8": ["blackman"], "10.9 20.6 15.1": ["flagellants"], "15.4 7.1 6.6": ["rogering"], "-3.5 2.8 -1.1": ["overutilized"], "6.7 27.0 6.9": ["slaveowner"], "-5.1 -1.7 -2.2": ["densitometer"], "5.0 18.5 12.1": ["forceably"], "18.1 14.1 18.7": ["hooo"], "4.2 7.8 -0.7": ["sufferd"], "10.8 3.5 4.7": ["dolar"], "0.0 18.1 8.3": ["pulic"], "13.5 19.0 2.7": ["soveriegn"], "18.8 8.7 4.4": ["bottleshops"], "1.1 27.9 6.2": ["perservere"], "7.4 7.7 7.4": ["sanskrit"], "0.7 15.8 5.3": ["deadbolted"], "1.7 6.5 11.2": ["hematized"], "31.3 20.4 10.3": ["tentacular"], "17.1 -3.4 17.4": ["bration"], "3.0 -8.5 9.1": ["vatu"], "-5.0 12.3 10.4": ["batswomen"], "9.2 4.9 22.3": ["sportsboat"], "3.1 -8.5 18.3": ["regis"], "10.0 7.8 0.4": ["exsisting"], "-0.3 2.3 4.8": ["flowrate"], "12.4 6.5 19.5": ["metazoans"], "11.3 12.0 13.0": ["welted"], "9.2 11.1 15.3": ["dystrophic"], "3.7 -11.2 13.0": ["zoh"], "15.3 15.6 18.1": ["mislocated"], "4.9 9.0 8.5": ["tym"], "4.1 12.7 3.2": ["oppourtunity"], "9.3 13.4 8.8": ["probabilistically"], "16.7 1.5 23.4": ["sgn"], "11.6 3.2 13.3": ["quadrupleheader"], "8.8 -0.1 5.9": ["superlow"], "20.3 1.5 12.7": ["crete"], "16.0 15.4 18.5": ["fkn"], "8.1 23.6 10.9": ["epaulet"], "18.7 8.2 14.6": ["uninflated"], "7.2 -3.9 12.7": ["pds"], "1.5 6.1 -0.6": ["kosh"], "-0.9 21.6 5.0": ["swayamsevak"], "10.0 1.9 7.5": ["allemande"], "14.0 8.7 18.4": ["boohooing"], "5.3 23.6 4.6": ["keycode"], "-3.1 3.2 3.9": ["defen"], "8.6 8.6 13.0": ["graff"], "1.8 22.9 0.1": ["opression"], "1.4 14.1 12.4": ["yuvraj"], "9.4 5.8 7.7": ["dogwalkers"], "1.1 4.3 7.0": ["sadak"], "-1.1 -6.8 6.6": ["medspas"], "17.0 5.4 5.2": ["engery"], "1.9 -3.7 5.1": ["cmi"], "9.9 5.6 12.8": ["doujinshi"], "-4.3 13.2 8.5": ["severalfold"], "1.1 8.0 14.0": ["swarmings"], "0.0 5.7 19.8": ["lambed"], "13.1 1.5 1.4": ["ercent"], "-2.5 8.1 1.4": ["ibooks"], "9.1 10.2 9.2": ["restrainer"], "13.5 11.3 13.1": ["nosecap"], "5.8 15.1 4.1": ["watchout"], "5.6 33.2 3.1": ["forgiver"], "15.0 4.7 14.8": ["gele"], "6.8 13.8 23.2": ["fluridone"], "-2.1 10.0 17.2": ["hanai"], "10.5 13.8 4.9": ["blackmarketeers"], "13.7 9.6 4.3": ["chromic"], "0.7 1.6 -0.5": ["upsampling"], "9.6 24.3 8.9": ["intelligencia"], "4.0 7.0 -0.1": ["haziest"], "14.6 1.7 6.6": ["onedotzero"], "7.2 26.9 8.6": ["commo"], "3.9 4.8 5.6": ["pricepoints"], "3.3 19.2 6.0": ["indegenous"], "8.9 10.0 12.0": ["kneepad"], "17.2 17.1 7.6": ["cinemagoer"], "14.8 17.6 13.7": ["cacaphony"], "3.7 5.6 10.2": ["aare"], "10.6 10.8 30.7": ["ahu"], "-5.2 10.2 12.8": ["debrided"], "7.2 2.4 8.7": ["photomicrographs", "spes"], "7.0 16.8 6.1": ["recontextualized"], "-2.5 9.8 2.8": ["typescripts"], "8.9 20.7 17.4": ["siree"], "1.4 9.6 1.1": ["callling"], "23.8 5.1 40.4": ["peapods"], "2.9 19.5 12.5": ["thakur"], "5.0 15.7 13.3": ["spotfest"], "8.8 1.1 5.5": ["urt"], "14.9 11.8 21.7": ["hartebeest"], "9.7 2.5 12.2": ["profilin"], "0.5 10.2 7.3": ["heartburns"], "4.9 8.5 12.4": ["rangey"], "15.7 -5.6 -4.1": ["equivelent"], "-0.1 4.6 -0.3": ["misconnections"], "17.7 28.5 14.2": ["unheeding"], "-1.3 8.8 15.1": ["indirects"], "11.6 2.8 5.7": ["immunostimulant"], "9.1 7.0 24.5": ["whitewood"], "5.2 -1.4 16.9": ["genebank"], "1.9 0.9 -2.2": ["nonmajor"], "14.8 4.7 31.5": ["jiaozi"], "0.5 4.6 8.4": ["leen"], "11.8 11.1 4.8": ["spectroscopically"], "5.0 8.5 12.3": ["runchase"], "2.7 -3.7 -0.3": ["adminster"], "15.3 9.3 11.6": ["lessly"], "3.5 -1.6 12.3": ["osteochondral"], "15.8 11.9 15.3": ["isbeing"], "-0.3 17.1 10.7": ["nonlinearities"], "4.8 11.2 10.9": ["odubtaig"], "1.2 5.6 4.1": ["storagematt"], "13.6 1.6 3.0": ["decelerator"], "19.1 12.4 14.6": ["hardbody"], "6.5 15.8 10.5": ["consolingly"], "4.1 34.0 8.7": ["oponent"], "11.6 5.2 6.9": ["defogger"], "20.6 18.8 14.7": ["gimbaled"], "6.7 11.0 9.3": ["wackadoodle"], "-4.0 7.0 5.7": ["governances"], "9.2 1.4 11.5": ["scriptorium"], "3.5 -2.6 11.7": ["matins"], "4.4 17.1 7.2": ["unfitted"], "0.2 3.5 10.2": ["unvoted"], "5.6 6.0 6.5": ["eni"], "8.1 18.7 15.1": ["cuckolds"], "7.2 18.0 17.8": ["pendatang"], "2.3 0.6 16.0": ["campdrafting"], "4.0 2.9 13.6": ["mixability"], "5.7 7.7 11.7": ["tonigh"], "8.2 14.3 0.9": ["overreport"], "0.4 6.7 14.1": ["refeeding"], "12.1 30.9 26.1": ["conspecifics"], "5.4 10.5 0.6": ["electroencephalograms"], "12.5 18.0 18.1": ["animalism"], "5.6 2.2 14.4": ["asphaltic"], "13.0 11.8 6.5": ["governmnent"], "6.5 18.2 -2.6": ["whohad"], "5.2 25.8 24.8": ["overcard"], "-4.9 21.8 3.0": ["interferance"], "10.5 4.0 11.9": ["junkshop"], "6.5 -4.8 18.0": ["biodegradables"], "17.5 14.5 12.1": ["bitmapped"], "6.5 6.0 11.1": ["hasnot"], "10.2 15.3 11.2": ["sublevels"], "5.5 9.3 -0.2": ["accurateness"], "11.0 5.3 17.6": ["cyclamates"], "-0.4 10.6 8.5": ["discpline"], "3.3 11.0 7.8": ["sian"], "6.5 12.9 3.2": ["fve"], "7.4 29.8 6.7": ["bandwagoning"], "17.4 8.3 23.3": ["toyon"], "9.0 12.2 8.8": ["crankily"], "3.3 10.4 11.5": ["rodriguez"], "10.6 8.0 -1.5": ["wasin"], "3.4 19.8 5.2": ["buddhism"], "-7.8 2.8 -1.3": ["votegetter"], "-0.6 18.9 6.3": ["haya"], "13.1 13.2 13.5": ["apetite"], "-2.8 0.9 10.5": ["dona"], "0.6 26.0 3.7": ["mahdi"], "6.1 5.2 6.7": ["fluegelhorn"], "1.2 8.6 8.7": ["corehole"], "13.3 13.2 17.4": ["overbred"], "6.2 10.7 5.0": ["ambiances"], "9.7 16.5 9.8": ["multibaggers"], "13.1 6.9 11.1": ["stich"], "1.3 3.3 4.5": ["trav"], "10.6 15.7 -3.6": ["theor"], "9.4 21.8 17.3": ["coccidia"], "9.5 -9.1 14.7": ["nappa"], "-1.5 -2.7 4.0": ["ascompared"], "-6.6 3.1 5.5": ["pouchitis"], "2.4 4.7 6.3": ["grantmaker"], "2.5 2.4 4.3": ["dtd"], "-1.1 19.0 8.2": ["overexerting"], "-8.5 5.0 6.9": ["gups"], "2.1 21.8 -0.3": ["fomenter"], "14.0 9.0 7.9": ["hexapod"], "8.1 6.9 5.8": ["damanged"], "14.8 17.3 38.0": ["loach"], "22.6 11.0 23.7": ["arbours"], "8.9 7.8 5.2": ["repossessors"], "-2.3 6.0 -0.9": ["agonism"], "13.8 11.4 13.6": ["subframes"], "18.5 19.3 16.6": ["turnstyle"], "6.4 26.5 -3.3": ["mutinying"], "-0.3 -1.4 9.7": ["teeball"], "16.7 30.2 42.6": ["greenhead"], "13.3 28.5 13.5": ["putin"], "5.3 10.3 21.6": ["simsim"], "-1.1 3.9 4.8": ["cefazolin"], "7.3 6.8 14.4": ["lipliner"], "0.5 -0.6 1.0": ["conferencecall"], "17.3 3.7 15.8": ["gbr"], "10.7 15.0 9.3": ["demonstators"], "5.2 15.4 15.0": ["endeth"], "23.7 16.1 13.7": ["swallower"], "20.9 12.8 20.5": ["unbruised"], "1.7 1.8 6.4": ["khz"], "7.3 12.3 7.3": ["caricatural"], "13.2 19.6 19.0": ["wigger"], "7.7 7.5 24.0": ["phan"], "18.9 13.6 1.5": ["syllabary"], "6.8 7.3 14.1": ["clientel"], "2.2 13.9 11.1": ["unrhymed"], "17.3 8.2 14.2": ["gobshite"], "5.2 11.4 17.6": ["blockiness"], "3.8 20.1 10.0": ["hyperrealism"], "11.1 18.7 21.9": ["hurricarana"], "9.4 7.9 10.2": ["redecorates"], "4.6 13.5 15.6": ["sluttiness"], "7.3 6.1 -2.2": ["inve"], "7.6 1.5 -8.5": ["opthamology"], "6.6 3.5 11.3": ["adipokines"], "8.2 -7.3 3.8": ["smiliar"], "5.0 0.9 2.4": ["ulipristal"], "24.4 24.0 17.6": ["putrescent"], "-0.2 4.6 3.3": ["diffusivity"], "9.8 4.2 10.9": ["granulates"], "-0.5 7.2 5.2": ["rahega"], "13.6 3.5 21.4": ["parquetry"], "2.6 5.1 3.6": ["panapress"], "0.8 3.6 7.4": ["rie"], "6.1 12.2 16.9": ["flyest"], "3.9 5.1 -5.1": ["transcranial"], "19.3 13.2 6.3": ["cyberchondria"], "3.7 10.4 5.8": ["elegaic"], "2.3 -2.5 11.2": ["dungkhag"], "-2.6 6.4 4.7": ["idraparinux"], "21.0 8.9 9.6": ["headily"], "11.2 12.6 8.1": ["iamdiddy"], "-0.4 7.8 2.6": ["libc"], "-0.8 5.9 8.2": ["langer"], "3.6 14.0 1.6": ["depersonalisation"], "12.3 17.0 24.0": ["shovellers"], "11.3 -1.8 1.0": ["supended"], "1.1 7.7 10.6": ["alvespimycin"], "14.4 22.4 12.5": ["squeamishly"], "11.1 9.8 10.7": ["abeg"], "4.2 5.6 8.6": ["orphanhood"], "9.9 8.7 11.3": ["noncorrosive"], "-2.5 1.9 21.6": ["parr"], "7.4 -0.8 10.4": ["hydrolysates"], "12.4 5.8 19.5": ["leno"], "8.9 7.5 14.6": ["xn"], "6.5 7.4 13.1": ["abajo"], "16.6 -2.2 6.5": ["bllion"], "6.9 7.0 6.4": ["neighourhood"], "1.0 11.0 7.3": ["beyound"], "-6.4 15.6 16.8": ["larvaciding"], "10.1 10.2 7.4": ["isstill"], "10.2 9.8 9.8": ["sexytime"], "-8.6 -4.4 1.9": ["chosed"], "12.3 13.4 13.5": ["intrapreneurship"], "-2.3 3.3 7.8": ["multirate"], "13.0 16.1 8.0": ["fuddled"], "11.4 26.1 6.6": ["preceived"], "-0.2 -6.6 2.4": ["ayt"], "17.2 10.1 21.9": ["spile"], "8.7 9.8 22.6": ["martingale"], "7.8 6.5 18.1": ["snugger"], "16.3 4.9 30.0": ["gingerroot"], "8.2 1.9 3.5": ["claimholders"], "-3.2 8.2 7.1": ["indiv"], "6.7 -8.4 9.3": ["ironer"], "10.7 23.6 12.8": ["dobber"], "3.1 0.1 8.9": ["delimiter"], "25.4 16.5 18.5": ["braining"], "8.5 -1.4 6.7": ["riverport"], "1.0 7.7 -0.6": ["inititative"], "0.9 -5.2 6.9": ["menor"], "1.4 6.8 12.6": ["powerdvd"], "3.3 -0.4 9.1": ["agre"], "7.1 14.1 12.6": ["unsurfaced"], "10.8 12.8 14.8": ["cking"], "3.1 10.9 16.6": ["nociception"], "0.8 19.8 11.8": ["bomohs"], "15.2 5.3 47.5": ["rockweed"], "0.7 13.7 18.4": ["epistasis"], "12.9 11.5 11.5": ["metagenome"], "6.8 4.5 9.8": ["economi"], "20.2 10.7 6.4": ["voa"], "4.7 12.6 15.9": ["voluptuary"], "12.2 1.2 6.7": ["repositionings"], "-2.7 12.1 8.9": ["kriya"], "5.7 25.7 10.8": ["trammeled"], "5.8 2.9 3.0": ["stehen"], "11.8 24.9 1.1": ["reforged"], "10.6 8.0 -1.3": ["convered"], "6.5 13.0 24.1": ["tesserae"], "19.3 15.4 10.5": ["typosquatters"], "8.6 21.5 0.7": ["expatriating"], "19.2 11.2 8.7": ["broadscale"], "4.4 -1.2 2.0": ["washbag"], "21.1 14.9 5.2": ["smuggest"], "10.1 9.8 16.1": ["purling"], "2.3 9.4 11.4": ["corel"], "0.3 -0.8 11.5": ["sightreading"], "3.9 6.7 17.2": ["yone"], "16.1 3.4 25.2": ["guanaco"], "9.4 -0.2 8.8": ["borosilicate"], "-5.3 0.5 3.0": ["kaur"], "7.4 4.4 5.3": ["reweighted"], "21.0 11.1 18.8": ["boogeying"], "12.2 16.1 9.9": ["oppenents"], "3.8 3.8 10.3": ["guggul"], "-0.6 13.6 3.4": ["disinviting"], "10.2 0.8 38.5": ["osetra"], "7.3 3.5 20.4": ["showring"], "2.6 2.5 8.6": ["diglycerides"], "13.1 3.1 16.8": ["housie"], "11.8 4.4 -0.9": ["ipernica"], "1.1 10.7 17.7": ["grainbelt"], "1.1 5.6 3.0": ["chron"], "5.0 -1.0 -4.9": ["follo"], "17.6 3.3 12.0": ["larg"], "10.9 5.9 1.9": ["productsand"], "10.1 7.7 4.7": ["exemple"], "15.2 15.6 32.7": ["ninebark"], "3.8 6.5 12.1": ["polymerize"], "6.8 8.3 13.0": ["pis"], "4.5 10.7 2.1": ["malayalam"], "0.4 2.5 13.8": ["nongolfers"], "8.4 4.5 6.6": ["substitutive"], "13.6 12.3 30.7": ["anisette"], "5.9 6.0 1.0": ["xeroxed"], "-3.6 8.8 7.6": ["agp"], "10.2 -0.5 13.2": ["arriba"], "1.0 9.1 16.4": ["sabihin"], "0.9 -6.7 -6.0": ["nica"], "16.4 11.2 25.5": ["nonindigenous"], "3.0 20.1 14.1": ["consequenses"], "13.6 9.4 10.6": ["nonpharmaceutical"], "7.8 1.3 19.8": ["hydroseeding"], "11.7 2.2 19.7": ["sli"], "4.6 15.7 12.8": ["forgivingly"], "5.2 23.1 5.0": ["deistic"], "16.9 10.8 13.3": ["chainsmoking"], "2.9 15.1 6.0": ["observors"], "7.0 12.8 12.2": ["spf"], "4.2 20.3 3.0": ["memorises"], "11.2 19.9 7.2": ["celly"], "-1.1 3.8 21.1": ["palagi"], "9.0 10.0 0.6": ["reflag"], "-5.5 13.9 8.8": ["rhinorrhea"], "1.2 16.5 4.3": ["supertaskers"], "-0.9 15.1 5.4": ["tauopathies"], "0.9 -6.3 2.9": ["metrologist"], "6.5 -0.6 1.7": ["microgenerator"], "13.9 7.4 15.6": ["slattern"], "-6.8 10.4 7.3": ["pesantrens"], "3.3 11.8 15.4": ["baal"], "6.1 -5.2 10.9": ["groundwood"], "3.2 10.4 -2.2": ["telecoil"], "4.8 14.9 4.8": ["whinier"], "-7.0 -0.1 8.2": ["pendings"], "2.6 8.5 17.3": ["unroasted"], "3.9 10.5 20.0": ["communis"], "12.3 -3.5 11.0": ["propanediol"], "24.3 10.6 1.5": ["electical"], "3.9 -5.4 10.0": ["viscometers"], "0.8 13.3 6.8": ["bacame"], "-1.3 2.1 12.7": ["peth"], "3.8 6.2 3.3": ["guily"], "-1.6 3.8 0.7": ["cinestar"], "-2.1 8.9 1.1": ["unstabilized"], "14.1 -0.1 12.6": ["gelaterias"], "7.5 11.5 18.3": ["beamsplitter"], "-1.9 5.1 6.9": ["wagner"], "2.2 0.6 9.2": ["nari"], "3.0 9.9 10.4": ["devadasis"], "1.6 16.3 4.0": ["tremedous"], "7.7 12.4 20.7": ["lttle"], "4.5 9.0 3.6": ["hypericum"], "-6.3 8.5 10.1": ["stikeouts"], "5.6 10.4 31.3": ["cheffy"], "9.8 6.5 6.8": ["activisits"], "-7.1 19.0 3.7": ["rahman"], "16.3 -3.5 1.9": ["foran"], "14.2 5.6 32.0": ["coatis"], "8.7 7.7 7.4": ["imf"], "5.8 -2.5 12.6": ["goldsmithing"], "8.4 4.2 2.5": ["eratic"], "1.9 9.6 3.7": ["drophouse"], "22.6 7.5 25.0": ["pedalos"], "11.9 5.7 23.4": ["aframax"], "-0.0 8.0 13.6": ["saja"], "0.9 4.5 2.2": ["breifly"], "2.8 3.9 -6.0": ["liaisoning"], "8.5 3.6 10.4": ["cachets"], "2.9 4.8 -0.8": ["biofluids"], "17.6 20.9 23.0": ["inchworms"], "9.3 18.9 25.1": ["griz"], "10.0 20.1 0.6": ["indepedence"], "7.4 -1.0 3.8": ["prebankruptcy"], "-10.7 14.3 -0.3": ["mnay"], "15.1 18.5 5.6": ["revenant"], "17.8 16.3 3.8": ["infantilising"], "3.1 7.7 4.3": ["neptunium"], "7.2 6.3 6.1": ["carphedon"], "-2.9 5.8 1.1": ["converstion"], "7.4 18.4 12.8": ["fark"], "18.6 27.1 23.6": ["cammo"], "6.3 4.2 11.7": ["skybridges"], "-1.4 2.7 11.5": ["dramady"], "12.3 -1.4 -2.2": ["distri"], "26.4 0.3 6.1": ["infocom"], "3.0 8.3 12.7": ["respins"], "-2.2 13.6 11.5": ["decimeter"], "-1.2 7.5 5.8": ["hysteretic"], "7.5 6.7 15.1": ["decling"], "7.4 4.7 13.4": ["vaping"], "11.8 -0.3 10.6": ["revenu"], "18.0 4.4 1.0": ["awaked"], "18.1 19.3 22.3": ["scrag"], "0.8 6.4 4.6": ["werre"], "9.2 20.7 12.6": ["insubstantiality"], "9.1 13.6 13.8": ["mclaren"], "8.2 10.1 12.8": ["mountainbikers"], "10.0 20.6 15.9": ["tinkerman"], "11.0 7.4 6.7": ["firehalls"], "1.3 7.0 4.7": ["legman"], "8.1 19.2 22.1": ["spading"], "17.0 27.2 11.6": ["numskull"], "4.6 2.7 10.6": ["greencard"], "8.2 7.3 -8.7": ["penman"], "5.6 1.1 8.7": ["qa"], "-14.3 7.3 0.4": ["committeed"], "3.0 11.9 19.5": ["miticides"], "8.9 -0.1 17.4": ["landbridge"], "17.0 11.6 11.1": ["velcroed"], "2.1 9.3 -0.8": ["subchannel"], "-4.1 18.4 6.5": ["nonexpert"], "10.7 6.9 11.1": ["innocuousness"], "11.9 0.1 32.7": ["marinaded"], "-5.1 11.5 4.4": ["lese"], "2.5 6.2 6.4": ["driv"], "7.9 12.7 2.8": ["welche"], "-3.5 10.5 3.3": ["nmi"], "19.0 14.1 10.4": ["barrowload"], "-2.4 17.0 8.3": ["strickly"], "4.0 10.3 0.3": ["chrominance"], "9.9 20.8 9.4": ["theirown"], "2.1 10.7 3.9": ["inviter"], "11.0 25.6 4.2": ["datalinks"], "18.1 2.9 17.6": ["tatas"], "-5.3 18.6 15.2": ["infinitives"], "10.6 5.6 17.6": ["toyboys"], "6.3 8.9 20.3": ["jenna"], "19.1 3.6 37.8": ["scows"], "13.1 1.3 7.6": ["entrada"], "5.1 -5.4 1.2": ["subcription"], "0.6 20.1 7.7": ["abilites"], "6.6 4.0 3.9": ["singsongy"], "-0.9 15.8 10.7": ["rino"], "3.3 23.4 1.2": ["depoliticization"], "5.8 5.5 2.8": ["psychophysiology"], "18.5 8.1 33.5": ["niblets"], "9.5 10.7 19.0": ["biogeographical"], "4.3 4.7 9.6": ["jonas"], "-7.5 -2.7 5.7": ["malate"], "20.0 10.3 27.7": ["cowslips"], "3.1 11.6 8.1": ["wavebands"], "-2.3 3.5 10.2": ["osteotomies"], "-1.4 5.0 5.2": ["cholangitis"], "14.9 0.0 4.9": ["grp"], "14.2 8.2 6.1": ["enchanced"], "15.3 -0.9 5.2": ["desulfurize"], "16.5 19.6 13.7": ["hided"], "18.6 16.0 15.1": ["punchbags"], "-5.7 11.5 7.4": ["reaggravate"], "18.7 9.3 5.5": ["horniest"], "4.4 -0.3 3.1": ["caisses"], "5.6 2.6 38.0": ["taramasalata"], "14.8 11.7 28.1": ["yellowhammer"], "7.2 11.2 9.8": ["amygdalae"], "-4.3 18.9 8.8": ["iterator"], "-1.7 10.5 5.9": ["assertedly"], "4.4 13.3 11.9": ["speedbreakers"], "4.5 1.8 9.9": ["seveal"], "6.4 3.1 3.6": ["oye"], "5.4 20.4 6.7": ["kkk"], "4.7 5.5 16.4": ["percale"], "8.3 6.9 9.9": ["hydroxylation"], "0.5 7.7 18.2": ["aglianico"], "6.7 6.3 10.4": ["reticular"], "-1.9 5.5 17.4": ["deciliter"], "11.4 2.2 45.7": ["bonitos"], "-2.7 5.1 7.3": ["stratifications"], "10.0 19.4 14.4": ["loserdom"], "16.4 12.3 5.4": ["advertisings"], "2.2 3.5 4.6": ["invitiation"], "1.0 20.2 10.0": ["burnover"], "12.1 10.8 12.7": ["cooky"], "6.2 14.7 5.5": ["wewill"], "11.5 12.9 16.1": ["dayum"], "5.5 6.8 10.1": ["taillamp"], "13.2 12.8 24.3": ["quarrymen"], "-4.0 -5.3 4.2": ["thankfull"], "9.1 1.3 21.1": ["pleurocoelus"], "4.5 9.3 19.5": ["dogless"], "7.6 7.1 13.5": ["unbathed"], "9.7 10.6 1.3": ["orother"], "7.2 12.3 -0.5": ["chamionship"], "-3.3 6.2 10.7": ["khushi"], "7.4 9.6 16.0": ["transgenesis"], "-5.0 -3.6 -5.1": ["plecanatide"], "15.2 15.6 19.5": ["trundlers"], "16.4 11.1 19.9": ["parterres"], "-2.9 25.3 2.0": ["extrajudicially"], "8.9 13.0 9.8": ["noised"], "6.8 9.5 8.2": ["sames"], "-2.9 -6.8 -3.2": ["attented"], "14.7 15.4 21.3": ["grrrrr"], "4.1 14.2 5.6": ["llike"], "-5.5 1.2 7.3": ["hensive"], "0.5 15.4 10.6": ["sira"], "6.7 6.5 6.7": ["millenary"], "10.0 18.4 11.3": ["ambulanceman"], "-8.1 24.8 -0.2": ["mudsling"], "-3.3 -3.7 2.6": ["psychopharmacologist"], "17.6 5.2 6.5": ["lubricator"], "13.9 -2.3 34.1": ["gambas"], "4.7 2.0 2.9": ["tranilast"], "21.2 18.1 37.4": ["gunnel"], "10.7 4.4 16.0": ["miters"], "10.7 6.0 5.8": ["staat"], "9.8 4.6 18.4": ["multitracking"], "5.6 -5.4 6.5": ["accordin"], "4.9 -7.3 3.6": ["eht"], "3.1 8.8 4.8": ["practive"], "4.3 11.3 10.9": ["jumpshooting"], "8.7 27.5 28.6": ["swarmers"], "20.6 11.6 14.9": ["shellsuit"], "16.9 14.4 34.4": ["buttah"], "18.8 13.1 -2.9": ["cablegate"], "-7.6 9.9 12.1": ["meas"], "-8.9 -4.9 1.8": ["enrollers"], "10.0 14.1 7.8": ["unscary"], "9.5 3.6 17.0": ["teragrams"], "0.3 10.5 -5.0": ["myjoyonline"], "8.5 5.9 13.4": ["constipating"], "-3.8 -6.3 -1.7": ["clincial"], "18.8 8.5 21.9": ["headshake"], "2.8 -4.3 20.2": ["vesper"], "16.4 -0.3 30.7": ["liquidiser"], "20.0 14.4 11.7": ["stormclouds"], "12.0 -1.8 2.6": ["ico"], "3.2 16.8 8.0": ["definitiveness"], "11.1 17.0 11.7": ["geesh"], "2.5 -0.4 11.3": ["otherfactors"], "10.6 6.0 9.8": ["karte"], "26.4 9.6 13.1": ["superduper"], "8.4 6.8 4.6": ["owne"], "13.3 22.0 18.7": ["putrefy"], "5.4 -0.2 21.3": ["ecotour"], "-7.6 4.9 7.5": ["deseg"], "12.4 2.7 5.8": ["sellthrough"], "8.3 10.1 15.6": ["enucleated"], "19.2 4.9 6.1": ["squiz"], "-0.6 35.0 3.0": ["mortarmen"], "14.1 3.0 33.6": ["taleggio"], "-5.0 18.8 -1.5": ["nontheists"], "8.5 -7.7 12.7": ["highweighted"], "16.0 17.7 16.9": ["stereovision"], "5.3 2.8 18.2": ["toc"], "12.4 15.0 14.2": ["occludes"], "15.4 9.7 24.2": ["gooing"], "18.5 12.7 12.7": ["piledriving"], "8.4 10.8 4.4": ["nomee"], "4.0 -7.5 16.4": ["zestier"], "1.9 10.6 15.4": ["beli"], "6.8 29.2 6.8": ["collaborationists"], "-0.9 -3.4 -3.4": ["defered"], "8.9 5.0 5.4": ["underbridge"], "11.2 4.9 31.0": ["siopao"], "17.5 5.0 20.0": ["swisher"], "17.3 14.9 28.5": ["cuddy"], "13.1 13.0 8.5": ["gallivants"], "6.7 6.1 10.2": ["kilomter"], "6.0 6.3 6.9": ["ordiance"], "1.0 13.3 3.1": ["deployees"], "1.9 18.5 7.6": ["heteronormativity"], "4.2 24.3 12.7": ["importune"], "6.4 5.1 6.6": ["twitpics"], "18.3 7.2 24.8": ["mallows"], "0.1 11.1 1.9": ["displeasures"], "5.2 9.6 14.8": ["frmo"], "-0.3 12.2 -0.1": ["multitronic"], "8.2 5.5 -7.0": ["hexamine"], "12.6 -5.6 36.2": ["mandu"], "7.6 34.5 18.0": ["fusiliers"], "7.7 9.5 42.0": ["eeling"], "9.0 3.9 11.5": ["towne"], "2.3 1.7 18.6": ["sungkai"], "6.2 0.9 5.5": ["cyclepath"], "3.2 8.1 6.0": ["extractives", "libber"], "13.3 10.1 14.4": ["washup"], "0.6 16.4 1.5": ["proned"], "11.2 3.3 4.9": ["freetrade"], "-6.1 6.6 4.5": ["demyelinating"], "10.9 14.3 13.6": ["liquifying", "catastrophism"], "8.5 11.4 7.2": ["overleverage"], "15.5 12.0 17.8": ["tailstock"], "9.4 0.2 14.6": ["bikefest"], "-1.7 9.3 9.0": ["ffmpeg"], "15.8 -2.1 -0.3": ["nebusiness"], "7.8 12.4 7.1": ["unharmonious"], "8.5 3.3 1.4": ["radiochemicals"], "17.0 3.9 5.1": ["buckminsterfullerene"], "14.8 9.8 19.1": ["tushies"], "7.7 11.4 5.2": ["creakiness"], "1.6 1.1 0.9": ["eac"], "30.2 27.1 7.5": ["telescreen"], "21.5 18.1 14.0": ["gadgeteer"], "15.2 6.7 15.2": ["unpromisingly"], "8.4 15.1 5.4": ["talen"], "10.1 1.1 17.4": ["phillip"], "3.6 18.7 3.4": ["outphysicaled"], "-10.9 -0.0 3.6": ["hyponatraemia"], "9.4 5.7 0.6": ["respone"], "2.0 6.4 12.1": ["ahas"], "1.2 8.5 5.3": ["peptidomimetic"], "5.8 20.7 7.6": ["unfactual"], "4.4 10.3 11.7": ["eversion"], "11.9 12.3 20.5": ["tallgrass"], "13.8 10.4 30.9": ["oared"], "6.3 13.4 4.6": ["serializes"], "9.6 0.5 10.7": ["biodeisel"], "6.3 12.2 17.3": ["roue"], "8.7 8.7 30.2": ["trematode"], "0.5 18.8 -0.9": ["casteless"], "3.2 7.1 0.7": ["decipherment"], "-0.4 4.9 3.5": ["glitazone", "xxxxxxxxx"], "6.2 12.2 2.5": ["hymned"], "4.8 9.5 19.0": ["kefi"], "2.9 -0.1 6.5": ["recor"], "-7.4 8.5 -0.6": ["performence"], "6.1 -7.7 7.2": ["rsums"], "3.8 10.9 19.9": ["elevational"], "-8.4 10.5 3.3": ["philosphical"], "6.6 10.6 10.7": ["dayparting"], "1.0 6.6 10.8": ["joshi"], "7.0 4.9 11.9": ["countermelodies"], "15.4 4.3 42.8": ["stockfish"], "10.2 15.7 13.8": ["tundras"], "11.0 7.6 8.6": ["capsulize"], "12.0 13.1 21.6": ["gapers"], "12.3 13.0 13.4": ["phils"], "-8.2 4.4 14.7": ["khal"], "10.1 0.9 10.5": ["garth"], "-2.3 14.7 8.0": ["predefine"], "2.7 -2.5 8.5": ["bioheat"], "1.2 6.5 -6.5": ["tooffer"], "-4.2 -6.7 2.7": ["nullnullnullnull"], "5.0 12.2 6.9": ["heighth"], "13.6 4.0 -2.4": ["datawarehouse"], "16.4 0.7 -0.2": ["fluorochemical"], "20.8 14.8 18.2": ["uncurled"], "21.0 37.4 19.6": ["ballista"], "20.0 16.2 15.9": ["redhot"], "5.8 17.1 2.3": ["believeing"], "6.1 1.8 14.2": ["expec"], "-5.4 7.9 -3.5": ["thecourt"], "6.8 13.3 4.2": ["housewifery"], "15.3 5.5 7.7": ["panelboard"], "11.2 9.5 3.3": ["bloggie"], "9.8 13.5 3.7": ["loopiest"], "7.4 4.4 14.9": ["hypertrichosis"], "3.8 -15.9 12.4": ["perfor"], "1.8 10.0 5.0": ["foramen"], "6.6 1.5 8.0": ["ultralong"], "0.9 15.2 6.3": ["informatio"], "5.7 6.8 22.6": ["heah"], "8.5 26.9 9.8": ["finiteness"], "-2.7 -0.3 4.3": ["durign"], "11.9 8.6 5.8": ["demonstate"], "20.0 23.0 24.4": ["gamesters"], "8.5 3.0 22.1": ["millas"], "13.2 -0.3 22.2": ["oilspill"], "14.9 9.5 0.8": ["geekspeak"], "10.2 8.0 12.6": ["souvenier"], "6.8 20.2 9.7": ["nihil"], "10.5 8.9 23.4": ["podding"], "13.3 12.4 12.0": ["kivas"], "0.5 14.3 8.6": ["moralized"], "9.6 10.6 1.4": ["geospace"], "7.7 8.4 22.6": ["jiang"], "14.4 7.6 18.0": ["sunshiney"], "-2.2 13.6 2.6": ["coaccused"], "10.6 26.6 -0.5": ["outmatches"], "17.6 2.6 12.3": ["effervescently"], "19.0 7.3 22.9": ["washi"], "19.5 4.1 25.6": ["isinglass"], "3.2 3.2 9.0": ["dnb"], "0.5 10.1 8.2": ["replicon"], "15.2 30.7 9.7": ["strategem"], "1.6 8.7 12.9": ["fibroadenoma"], "1.2 14.1 8.2": ["cancerdefine"], "23.9 8.8 7.6": ["tradin"], "9.8 4.0 4.0": ["friendlyway"], "4.9 2.3 9.1": ["ligne"], "6.3 14.3 7.3": ["noons"], "-1.0 12.0 6.8": ["unclarified"], "10.2 12.5 8.4": ["chivvied"], "17.3 20.1 14.9": ["macrocosmic"], "11.2 2.5 14.4": ["shipbroking"], "0.6 1.4 6.6": ["revist"], "8.4 8.3 12.9": ["trimers"], "11.6 11.7 13.0": ["depositers"], "7.7 2.8 4.6": ["eflornithine"], "-3.4 8.7 17.8": ["magsalita"], "-1.5 7.9 8.2": ["sgm"], "4.2 3.8 18.3": ["bedders"], "10.8 16.6 24.4": ["badonkadonk"], "4.2 3.6 -1.2": ["poetries"], "13.9 4.6 14.7": ["acerola"], "6.0 -5.2 2.8": ["mtpd"], "7.3 13.3 14.9": ["countermelody", "unspecialised"], "4.3 15.9 -1.3": ["secuity"], "-7.0 2.9 0.8": ["insite"], "18.4 13.9 23.3": ["titanosaurs"], "4.6 4.7 11.5": ["citybound"], "9.1 21.9 22.5": ["handywoman"], "9.3 13.6 15.4": ["homogenizes"], "10.9 11.9 8.6": ["trucklike"], "-3.8 4.3 2.6": ["paracentesis"], "1.7 20.3 18.3": ["guesstimation"], "8.2 13.1 25.6": ["herps"], "-6.3 2.4 8.2": ["serverboards"], "8.4 15.8 32.5": ["sloes"], "4.6 10.0 1.0": ["mineralising"], "9.1 4.2 7.2": ["autoroutes"], "1.8 7.2 -1.8": ["suretyship"], "1.1 5.9 25.5": ["barolo"], "14.6 15.2 14.5": ["farmville"], "11.6 13.7 14.1": ["votin"], "12.1 1.8 0.6": ["rollbars"], "17.6 10.6 19.0": ["seawards"], "1.6 1.9 2.6": ["lations"], "2.4 8.3 2.8": ["canakinumab"], "15.9 10.9 19.8": ["chaperonin"], "3.7 3.3 8.1": ["strate"], "15.0 5.5 -8.4": ["streetfootballworld"], "3.4 -8.6 6.3": ["signe"], "4.0 14.5 12.4": ["runthrough"], "5.3 10.1 13.0": ["cbc"], "4.9 8.2 13.7": ["volatilty"], "10.6 8.8 1.8": ["ennoblement"], "-4.7 0.2 11.2": ["microcoil"], "-4.0 7.4 -7.8": ["coauthoring"], "8.4 6.3 8.8": ["akhadas"], "14.4 1.0 10.7": ["cade"], "21.3 11.9 13.8": ["keyboardless"], "7.0 17.1 7.5": ["opprotunity"], "13.0 3.3 7.8": ["unstowed"], "0.5 4.6 5.6": ["teleseryes"], "4.7 9.0 5.9": ["euch"], "9.4 19.4 6.6": ["capturers"], "4.1 0.3 -1.7": ["digitale"], "9.1 13.4 9.3": ["curtseying"], "6.0 15.8 24.8": ["rototill"], "10.6 5.7 9.0": ["financal"], "3.1 13.5 9.2": ["guidons"], "0.1 9.4 -6.1": ["servce"], "11.7 0.1 6.6": ["barbing"], "10.4 18.1 13.1": ["queerly"], "1.5 8.8 4.5": ["restoral"], "18.7 12.5 29.6": ["gigantea"], "17.7 26.6 9.8": ["taunter"], "12.9 5.5 4.6": ["efforst"], "0.4 10.7 1.6": ["targetability"], "8.8 18.5 6.9": ["lobotomize"], "4.0 12.8 14.7": ["metacarpals"], "12.7 11.2 13.5": ["melismas"], "29.5 11.3 21.8": ["snaggletoothed"], "8.2 17.4 4.1": ["nucleon"], "-2.2 6.2 14.0": ["intertemporal"], "9.8 20.7 3.1": ["hurted"], "14.0 17.6 17.8": ["eusocial"], "8.1 11.9 25.0": ["karela"], "7.6 11.1 19.1": ["trisikad"], "2.6 13.7 6.9": ["improvisationally"], "20.4 -1.1 9.2": ["jointventure"], "1.1 2.3 9.8": ["borefield"], "4.2 5.1 2.8": ["weitere"], "7.4 8.1 6.9": ["uncompress"], "1.5 19.1 3.9": ["youngmen"], "1.5 19.0 11.0": ["acquaintences"], "15.1 7.8 8.8": ["litl"], "-8.9 19.1 2.0": ["denominationally"], "3.8 10.8 11.2": ["indio"], "9.1 6.5 13.4": ["unshoveled"], "-4.6 10.4 0.7": ["forour"], "7.1 15.7 5.1": ["interposes"], "5.5 15.6 12.9": ["castillo"], "10.6 -0.1 21.2": ["wichcraft"], "1.1 13.4 10.8": ["intracellularly"], "9.5 0.9 7.5": ["iirc"], "16.5 18.8 11.1": ["expectorating"], "6.9 5.7 4.0": ["copywrite"], "5.6 -0.1 14.8": ["chondrocyte"], "9.3 3.5 4.6": ["heartwarmer"], "12.1 14.6 1.4": ["bugginess"], "7.6 21.5 19.5": ["outlanders"], "5.5 20.1 13.2": ["unfortuantely"], "6.0 3.1 3.8": ["telphone"], "1.1 15.9 8.9": ["protagonism"], "4.2 7.3 8.1": ["pivotman"], "22.2 15.1 27.7": ["prows"], "0.4 20.0 5.8": ["equivalences"], "-2.7 3.9 6.9": ["posttrial"], "9.2 11.1 8.4": ["megadose"], "6.9 24.9 14.8": ["unkindest"], "-5.9 3.8 11.5": ["hypopigmentation"], "-5.0 9.3 15.0": ["kaitiakitanga"], "5.4 16.2 5.3": ["thorougly"], "11.4 18.5 15.5": ["scragged"], "16.5 15.1 27.2": ["boatful"], "0.0 15.5 5.6": ["mohammad"], "4.4 9.4 4.6": ["liberalisations"], "-3.0 3.9 1.2": ["provison"], "9.9 11.9 12.6": ["kinesins"], "2.9 8.4 12.7": ["volver"], "1.4 4.0 7.9": ["tendinosis"], "16.4 19.6 8.9": ["ownage"], "10.6 17.0 4.4": ["austrian"], "-1.8 17.4 9.8": ["snideness"], "0.2 14.2 11.9": ["kanamycin"], "4.2 -0.2 3.9": ["graphy"], "1.3 14.5 0.8": ["pyrophoric"], "4.8 -5.6 7.8": ["cass"], "9.2 13.3 19.7": ["boozin"], "-10.5 -6.6 5.1": ["reaccredidation"], "-3.4 19.7 4.9": ["conscientise"], "12.0 -0.1 8.9": ["naturalgas"], "-6.7 9.6 4.2": ["neonaticide"], "-3.8 5.9 0.1": ["disfellowshipped"], "2.7 18.0 12.0": ["topspins"], "-0.4 12.0 4.0": ["photolysis"], "9.8 0.5 11.9": ["joven"], "7.8 19.0 15.5": ["radiomen"], "10.5 14.3 4.6": ["esotericism"], "16.8 8.9 47.2": ["sandeels"], "-0.1 9.5 -9.5": ["thatthere"], "18.1 14.6 16.3": ["reredos"], "5.1 4.5 11.6": ["kennelling"], "7.5 14.7 14.6": ["vana"], "10.1 25.0 8.1": ["pratically"], "13.8 18.3 17.4": ["swoopers"], "-0.4 2.2 10.4": ["matside"], "2.4 4.6 5.1": ["partitas"], "12.2 5.4 6.0": ["antimalaria"], "3.8 -0.1 0.6": ["oman"], "-3.1 -2.9 12.6": ["procaine"], "1.2 12.2 7.2": ["antiangiogenesis"], "8.4 9.1 9.1": ["diverticuli"], "5.7 -6.3 1.6": ["sede"], "-2.8 6.3 10.9": ["grandaunt"], "15.4 2.0 13.2": ["sout"], "-6.1 14.0 -1.4": ["shaliach"], "10.7 9.1 2.4": ["ady"], "13.8 9.8 23.5": ["costas"], "13.4 8.0 11.7": ["bradford"], "-6.3 -2.2 10.9": ["binte"], "-0.7 13.2 3.4": ["personam"], "0.3 6.2 5.2": ["droperidol"], "17.7 8.1 5.3": ["hived"], "8.8 9.0 15.1": ["mwah"], "-0.2 7.8 7.4": ["rona"], "21.4 11.2 5.2": ["renationalized"], "-6.9 11.7 -7.4": ["commmitted"], "14.5 8.2 11.3": ["moneybox"], "7.7 9.2 8.8": ["informatie"], "2.8 8.7 3.5": ["fueding"], "13.6 4.9 22.8": ["hairclips"], "20.0 11.0 -0.5": ["awayfrom"], "-7.4 -0.0 5.9": ["bivocational"], "-1.6 13.8 -2.1": ["concordances"], "-4.7 2.6 15.5": ["euthanasias"], "4.8 0.5 10.8": ["importantes"], "-11.7 23.8 -5.4": ["jamaats"], "-8.3 9.0 5.7": ["trichomonas"], "0.6 6.3 0.1": ["accomadate"], "1.9 3.2 2.3": ["suggets"], "12.0 22.1 3.0": ["dopiest"], "14.2 14.3 13.9": ["coverd"], "-1.1 2.7 9.6": ["mabuti"], "-0.4 6.4 7.9": ["peroxisomes"], "8.6 4.3 13.9": ["chorded"], "3.6 -2.2 18.1": ["brighton"], "17.5 15.6 24.9": ["geotubes"], "-2.1 10.0 -1.0": ["eviti"], "10.8 17.1 7.9": ["thatcould", "lossess"], "3.8 4.3 4.9": ["efile"], "-3.4 -1.0 -5.7": ["liased"], "17.1 10.3 17.2": ["junkier"], "3.0 9.8 -0.2": ["stategic"], "12.4 2.5 18.6": ["spoonable"], "15.1 9.3 18.8": ["mirrorlike"], "2.5 3.9 6.6": ["panches"], "-1.1 12.7 12.0": ["fumblitis"], "12.4 12.6 12.0": ["anybodys"], "3.9 8.6 1.0": ["disapora"], "17.5 5.9 10.6": ["unrecycled"], "-1.7 3.0 3.5": ["iden"], "-6.4 6.9 -11.2": ["critising"], "4.1 20.4 8.0": ["whackjobs"], "2.8 6.1 6.9": ["nonirrigated"], "15.5 0.9 9.3": ["tique"], "7.2 9.2 -0.2": ["runnng"], "8.9 3.1 3.0": ["moblogs"], "12.2 13.1 13.9": ["decend"], "18.8 7.4 10.6": ["kipping"], "4.8 18.7 7.6": ["laogai"], "-2.7 10.1 17.2": ["diquat"], "-8.4 14.6 -1.6": ["theirself"], "7.1 0.4 8.8": ["cabala"], "2.4 11.1 7.5": ["retitling"], "13.2 7.4 9.7": ["axman"], "9.3 16.3 15.6": ["augering"], "2.6 5.8 7.3": ["moti"], "3.5 10.0 12.6": ["cruiselines"], "-5.0 -6.4 -0.7": ["consultors"], "13.8 6.4 10.2": ["similiarly"], "3.1 10.8 9.3": ["misregulation"], "0.6 -2.7 4.0": ["inger"], "17.4 20.7 10.2": ["buzzsaws"], "0.4 10.3 9.8": ["devin"], "-5.9 3.6 3.1": ["thexchange"], "2.7 2.2 9.1": ["homozygosity"], "14.5 8.6 18.0": ["effen"], "10.9 4.1 19.2": ["disp"], "14.2 -4.3 3.1": ["milliom"], "-2.1 8.7 8.8": ["jammu"], "10.2 41.0 13.1": ["jarheads"], "-9.8 4.8 9.9": ["nonhomestead"], "4.0 6.2 15.3": ["clostridium"], "-1.5 1.0 1.5": ["methoxy"], "12.0 18.5 9.5": ["easliy"], "4.0 -3.8 6.9": ["krooni"], "25.0 14.3 36.8": ["mollies"], "9.8 15.3 17.1": ["schwartz"], "8.5 -4.4 2.8": ["superabsorbent"], "1.8 0.6 17.1": ["kapas"], "5.5 25.8 11.4": ["imprecation"], "-4.4 17.2 5.2": ["collectivities"], "5.9 17.4 5.0": ["jaggedness"], "5.5 5.0 3.7": ["compliation"], "-2.2 3.9 4.5": ["remifentanil"], "8.4 3.3 -2.8": ["telecardiology"], "8.2 18.5 23.3": ["proverty"], "-0.6 0.0 6.8": ["cose"], "-0.9 11.3 13.7": ["preston"], "5.4 0.4 -3.1": ["gency"], "-11.1 5.5 2.5": ["thecommunity"], "-3.6 11.5 8.7": ["occurr"], "1.6 8.2 8.2": ["speek"], "16.0 2.3 17.0": ["capitalisations"], "8.2 18.2 14.9": ["depower"], "-5.5 12.1 -0.6": ["envolved"], "-0.4 18.7 8.9": ["standardly"], "1.4 19.3 9.2": ["pantheist"], "6.1 26.0 11.1": ["blunderer"], "10.6 18.6 -2.7": ["jounalists"], "10.2 6.4 12.6": ["monounsat"], "18.2 20.3 10.7": ["sluggards"], "2.4 17.5 5.1": ["videogamer"], "7.5 1.9 5.9": ["sideskirts"], "12.5 -6.5 8.2": ["drapers"], "13.2 8.7 37.6": ["redwing"], "-6.1 1.1 0.2": ["detrusor"], "14.3 12.9 12.1": ["superboot"], "2.8 6.6 11.8": ["vilage"], "-8.0 13.3 0.5": ["enclaved"], "1.7 10.8 2.3": ["youg"], "-1.1 9.2 14.1": ["trafficable"], "10.0 11.7 12.0": ["missals"], "17.0 14.5 8.5": ["commoditising"], "1.3 3.0 -3.0": ["ffrom"], "23.8 9.2 11.0": ["lightpoles"], "10.1 16.5 22.8": ["sinkage"], "7.5 6.7 16.1": ["positronium"], "11.8 30.9 13.3": ["barbarously"], "2.0 5.8 4.1": ["capitan"], "8.9 3.0 -3.3": ["scandel"], "10.6 7.4 16.8": ["batture"], "13.9 24.4 9.1": ["neos"], "5.3 8.6 13.3": ["laa"], "3.1 2.1 11.8": ["enterolactone"], "7.7 9.6 12.6": ["hillcrest"], "4.6 0.6 2.0": ["noticias"], "2.6 18.8 2.3": ["apolitically"], "8.6 9.7 18.1": ["washwater"], "12.0 12.5 15.0": ["fuhgeddaboudit"], "1.0 2.2 8.5": ["lill"], "6.6 6.3 7.9": ["wons"], "2.7 4.6 2.8": ["volociximab"], "5.3 2.0 13.1": ["dystroglycan"], "-1.6 9.8 0.8": ["reselect"], "8.5 6.7 14.5": ["pinna"], "7.1 21.1 2.0": ["foreswearing"], "1.5 4.3 8.1": ["antiparasitic"], "7.0 11.2 9.9": ["haba"], "6.6 15.2 10.3": ["unposed"], "6.6 13.4 10.6": ["hwo"], "6.1 12.9 9.0": ["lazybones"], "3.4 8.9 12.2": ["espically"], "-2.4 15.6 -2.9": ["oppossed"], "21.7 10.6 15.4": ["pertly"], "1.0 -1.2 5.3": ["stablization"], "4.5 14.3 7.2": ["blantant"], "12.3 8.2 11.0": ["doinked"], "15.7 9.0 11.9": ["verticalized"], "4.0 10.1 16.6": ["thuggin"], "13.1 -1.0 -1.6": ["aggregately"], "15.2 7.2 17.7": ["smartarse"], "-0.7 3.6 4.1": ["varous"], "15.1 3.9 27.5": ["untoasted"], "5.4 21.5 6.9": ["uniters"], "3.8 8.4 10.9": ["daycation"], "11.7 8.5 7.6": ["preapprove"], "-1.3 9.7 10.5": ["manaakitanga"], "2.0 4.1 7.0": ["befoe"], "3.0 -2.0 7.7": ["permanente"], "-5.3 21.5 -8.0": ["intercommunications"], "4.0 20.1 9.1": ["jounalist"], "15.4 8.0 17.1": ["chunkiest"], "-0.2 7.9 -3.2": ["dyssynchrony"], "10.1 5.5 4.1": ["mutualised"], "6.7 7.8 -0.6": ["cheerleads"], "1.5 7.4 10.8": ["chlamydial"], "0.4 6.7 11.8": ["rossi"], "14.6 15.1 9.6": ["refractors"], "-0.6 -1.9 -6.3": ["iving"], "11.6 11.5 17.9": ["zzzzzz"], "19.9 15.8 2.9": ["celluar"], "5.2 19.8 5.6": ["representatively"], "-8.3 16.3 -0.2": ["magistrature"], "20.6 8.5 16.6": ["peroxided"], "14.0 19.1 20.6": ["fuggedaboutit"], "10.5 21.4 7.3": ["slackjawed"], "3.7 18.0 16.3": ["wyodutch"], "2.6 4.2 12.7": ["bulbouts"], "2.4 8.6 4.6": ["oddsmaking"], "-8.3 8.0 6.0": ["palifermin"], "9.4 8.6 5.2": ["servicemark"], "-1.0 8.7 4.2": ["teached"], "4.9 3.0 8.1": ["automatable"], "0.9 1.0 -1.4": ["revisionary"], "-6.1 1.8 4.1": ["flutamide"], "4.6 8.0 11.2": ["oversinging"], "19.0 8.6 13.9": ["humongously"], "10.3 15.1 18.3": ["mangal"], "1.2 30.5 4.0": ["eliminationist"], "19.3 16.8 17.1": ["fulla"], "6.8 11.2 24.7": ["paspalum"], "-0.1 5.8 10.5": ["bumpouts"], "8.4 14.6 17.6": ["crosshead"], "6.5 -1.1 1.0": ["hyperintense"], "7.9 2.0 12.0": ["arati"], "-2.8 -0.1 -0.1": ["thienopyridine"], "0.1 18.6 24.3": ["ungrazed"], "4.8 16.0 5.2": ["substring"], "12.2 13.3 10.7": ["wheelwell"], "5.9 11.1 9.5": ["squeek"], "4.0 2.3 -6.4": ["ountry"], "19.4 7.1 14.2": ["towhead"], "-8.7 9.2 13.0": ["sesamoids"], "3.8 -6.3 5.1": ["premi"], "3.8 12.2 -4.8": ["immidiately"], "8.7 14.7 15.3": ["tableland"], "7.4 10.7 11.3": ["unpurified"], "1.8 19.4 20.5": ["overdressing"], "-10.7 8.9 3.0": ["alochol"], "-3.1 -0.7 4.4": ["cashbook"], "-5.6 0.9 15.1": ["isip"], "3.0 10.5 -4.9": ["reamin"], "8.6 -4.6 -2.8": ["presskit"], "1.5 8.9 6.0": ["reclassed"], "4.0 1.6 5.2": ["mec"], "-1.4 14.8 5.1": ["khuda"], "6.6 0.6 -0.8": ["vwd"], "0.1 4.6 14.1": ["paladars"], "15.4 13.8 32.2": ["bouys"], "1.7 21.7 11.0": ["fraternally"], "1.9 13.7 6.0": ["adays"], "20.2 13.8 12.2": ["larynxes"], "12.7 0.2 12.8": ["binbags"], "12.5 10.3 11.1": ["inhomogeneities"], "3.2 20.2 17.3": ["morphogen"], "4.9 2.2 8.8": ["wokerd"], "17.4 3.2 2.7": ["ultrabright"], "13.8 1.9 17.5": ["supergiants"], "13.3 28.5 17.1": ["inexorability"], "17.1 18.3 20.5": ["mulga"], "-10.1 16.4 6.3": ["parasha"], "4.1 11.4 11.5": ["allanite"], "7.3 27.9 6.8": ["annexationist"], "3.7 16.8 15.5": ["phosphonate"], "11.3 11.6 26.0": ["lespedeza"], "14.4 11.3 26.7": ["gamier"], "4.8 12.3 9.5": ["liquidly"], "3.0 9.1 12.8": ["coule"], "8.4 7.6 14.7": ["decomposable"], "1.1 7.4 11.7": ["chela"], "2.4 9.4 -2.6": ["retrofittable"], "18.0 11.4 24.5": ["thataway"], "10.8 18.4 10.3": ["villainously"], "13.8 2.6 15.9": ["longue"], "6.0 -1.9 7.7": ["intima"], "22.1 6.7 39.1": ["chatterbaits"], "6.4 9.3 10.4": ["midgate"], "7.3 29.9 1.1": ["destabilizer"], "10.3 -4.0 0.5": ["mnths"], "9.8 8.5 30.6": ["pasilla"], "0.6 3.7 7.4": ["eze"], "7.0 9.6 10.5": ["titlebar"], "9.4 9.9 7.4": ["drumbeaters"], "-3.7 0.8 18.3": ["interglacials"], "7.9 6.0 9.4": ["natters"], "16.5 -8.5 21.7": ["holstein"], "14.1 9.5 41.4": ["excluder"], "2.5 4.3 9.6": ["hizo"], "5.5 4.6 15.6": ["bandhgala"], "14.2 16.9 15.4": ["mebbe"], "15.1 9.2 12.1": ["corporatize"], "9.8 6.4 15.6": ["sandshoes"], "8.9 3.4 14.3": ["lispy"], "12.5 11.3 16.0": ["iceland"], "7.5 -2.6 17.7": ["geh"], "7.2 13.1 2.7": ["relevence"], "10.2 4.6 9.0": ["voiceprints"], "8.2 30.0 9.2": ["mugabe"], "6.4 1.0 4.0": ["bronchoscopes"], "11.5 13.9 2.9": ["cdma"], "17.6 18.6 26.2": ["sloe"], "12.5 -0.6 -0.3": ["leven"], "-3.7 18.3 12.0": ["canonists"], "-0.3 2.4 7.8": ["mammo"], "7.6 15.5 8.1": ["doink"], "7.4 5.8 14.7": ["comeliness"], "7.7 1.3 10.8": ["gelcoats"], "-2.9 3.8 4.4": ["nulle"], "-1.3 -1.4 5.2": ["physicial"], "-2.3 1.5 1.1": ["subtheme"], "5.6 15.9 8.2": ["italicizing"], "-2.2 10.1 11.5": ["alcalde"], "3.2 0.3 8.8": ["estoy"], "7.2 7.6 28.4": ["rau"], "1.4 21.3 4.6": ["positivistic"], "3.4 6.8 6.7": ["keywording"], "-0.8 31.1 16.4": ["hurtfully"], "6.3 1.5 10.7": ["bose"], "10.5 10.4 7.1": ["undertalented"], "5.4 6.0 4.3": ["featureset"], "7.8 4.1 1.6": ["dsicmm"], "1.9 26.5 -0.6": ["devide"], "24.0 25.9 7.6": ["vivisected"], "19.4 6.2 13.9": ["hicky"], "0.0 2.0 0.4": ["shedule"], "7.2 7.3 19.8": ["unpeel"], "4.1 12.1 17.7": ["basant"], "3.5 5.0 9.1": ["handcycles"], "14.0 4.5 15.0": ["bric"], "1.9 20.4 5.8": ["abhorent"], "13.7 21.0 4.1": ["appart"], "10.2 19.7 9.8": ["cagefighting"], "-4.1 1.6 6.2": ["interpellate"], "9.6 4.2 16.2": ["epiwafers"], "4.4 22.1 13.1": ["ballsier"], "8.9 23.0 17.8": ["somewheres"], "12.3 10.1 4.2": ["itouch"], "11.9 9.7 17.0": ["beerfest"], "6.3 15.9 9.9": ["pussyfoot"], "-11.9 1.9 3.5": ["cerclage"], "4.3 5.2 1.5": ["stellt"], "0.5 2.6 18.5": ["aki"], "5.2 9.0 9.1": ["payless"], "4.2 12.8 12.3": ["gallas"], "12.7 4.6 32.1": ["galax"], "2.6 11.4 10.0": ["wouild"], "-0.4 4.1 11.5": ["ayahs"], "20.7 8.3 38.2": ["conure"], "16.5 36.5 16.4": ["breastworks"], "12.8 12.0 5.4": ["asterix"], "-3.1 16.5 1.2": ["talkgroups"], "12.2 17.9 13.3": ["shakings"], "-2.6 -2.6 9.1": ["colligate", "lto"], "17.0 7.9 0.5": ["illfated"], "21.2 27.9 14.4": ["daleks"], "-2.4 -1.4 3.9": ["jointure"], "16.3 10.8 14.2": ["lighttpd"], "6.2 10.2 -5.4": ["belabouring"], "5.1 9.6 15.5": ["intermediately"], "13.6 2.1 8.0": ["pantsula"], "-1.1 -0.6 1.8": ["valvulopathy"], "4.9 17.9 13.0": ["daytrader"], "19.8 7.3 15.3": ["flatback"], "2.4 12.3 -1.0": ["shockable"], "23.4 38.5 16.8": ["chaingun"], "0.6 8.1 7.1": ["polyamorists"], "-1.5 5.9 9.2": ["kps"], "-5.6 5.9 6.3": ["nonconformities"], "16.9 26.2 4.3": ["ganked"], "9.1 6.4 6.3": ["magnetisation"], "4.1 12.0 16.4": ["tief"], "-6.2 17.4 11.0": ["belabors"], "11.3 2.4 -0.1": ["mishandlings"], "9.5 9.8 14.9": ["jornaleros"], "14.4 4.7 8.0": ["zh"], "2.9 14.5 5.3": ["angy"], "5.3 13.5 10.1": ["dest"], "-1.1 3.5 14.6": ["ili"], "17.4 -5.4 -3.7": ["ownes"], "-4.3 8.9 1.3": ["filiation"], "6.7 7.2 6.5": ["knickerless"], "7.8 2.1 32.8": ["asada"], "0.2 9.8 1.4": ["pledgee"], "-0.1 -1.5 11.0": ["restobar"], "8.3 14.4 10.4": ["estrangements"], "20.1 15.8 19.0": ["corncrib"], "17.7 14.5 19.4": ["domesticates"], "10.3 5.0 11.9": ["sheeters"], "8.1 9.9 8.7": ["amatory"], "10.2 2.9 8.2": ["openin"], "4.4 16.0 12.1": ["netcode"], "4.6 10.4 12.4": ["obliqueness"], "8.8 32.5 7.6": ["sith"], "15.2 0.8 12.4": ["medford"], "24.3 14.0 40.0": ["moray"], "5.9 11.1 8.7": ["thymidine"], "15.5 14.5 13.0": ["jemmy"], "10.5 11.2 20.1": ["serena"], "10.1 -0.9 16.8": ["deadlifting"], "2.4 5.2 3.4": ["eritoran"], "-3.8 16.5 14.4": ["noor"], "4.0 -1.5 30.0": ["savoy"], "4.2 3.4 6.1": ["tambien"], "2.3 6.4 4.7": ["manumission"], "0.2 8.9 0.3": ["lude"], "-3.1 4.7 4.3": ["weil"], "-1.2 16.0 6.2": ["accretively"], "17.1 21.7 14.8": ["clingers"], "0.6 7.1 -0.3": ["obwohl"], "5.2 8.1 15.0": ["chrysocolla"], "22.9 19.5 11.7": ["lightcycle"], "11.1 15.4 19.4": ["supercooling"], "19.7 16.6 9.0": ["anglophiles"], "12.2 17.8 23.6": ["cockleburs"], "7.1 15.8 17.8": ["mardy"], "6.9 9.6 11.2": ["overindulgences"], "8.1 9.4 4.8": ["toreach"], "-2.6 4.5 -0.2": ["receiveing"], "1.9 10.8 19.5": ["subbase"], "16.1 11.5 -0.4": ["strking"], "-7.3 9.3 -1.5": ["nti"], "21.0 3.7 27.1": ["tailer"], "15.2 6.6 8.6": ["parping"], "10.3 7.8 12.0": ["checkweighing"], "-7.7 10.0 2.2": ["payam"], "-5.2 8.6 10.0": ["hil"], "8.3 18.0 44.3": ["albies"], "-5.5 4.6 8.7": ["serverboard"], "7.0 13.0 8.3": ["manglik"], "-0.3 5.6 14.1": ["respin"], "-3.1 4.0 5.9": ["rediagnosed"], "13.7 0.8 11.4": ["acu"], "-6.3 12.8 5.5": ["histologies"], "8.4 14.8 11.7": ["appurtenance"], "10.8 4.7 30.6": ["foliages"], "10.2 9.9 20.0": ["westcoast"], "-0.5 -0.4 0.9": ["flunitrazepam"], "9.2 3.3 -5.3": ["deconsolidating"], "15.0 12.3 23.4": ["whipworm"], "10.5 13.3 11.2": ["prople"], "2.2 10.4 12.8": ["cryptococcosis"], "10.2 0.0 36.8": ["longganisa"], "-5.7 8.2 8.1": ["precentage"], "21.1 5.9 2.6": ["beancounter"], "10.2 12.8 13.8": ["plier"], "11.1 9.1 17.4": ["kanwarias"], "-9.5 27.9 6.8": ["pararescueman"], "-1.4 3.8 9.2": ["delineator"], "-0.4 15.3 11.7": ["whininess"], "3.7 0.3 9.2": ["rampup"], "25.6 11.7 17.3": ["pooed"], "7.1 11.3 12.2": ["nonabrasive"], "-9.5 4.0 -0.4": ["warrantholder"], "-9.0 12.6 -0.4": ["deontological"], "-1.5 9.5 21.1": ["nonrural"], "7.4 9.5 18.9": ["kumbh"], "-0.0 6.2 6.6": ["ultramarathoners"], "-10.6 0.8 1.2": ["abstractor"], "4.7 4.0 9.8": ["pegaptanib"], "1.6 7.1 8.4": ["retros"], "10.6 19.4 38.7": ["hookset"], "9.1 7.4 26.1": ["shmear"], "13.8 10.4 23.6": ["scrumptiously"], "15.4 13.9 6.8": ["megavendors"], "4.9 18.5 25.0": ["restack"], "7.0 2.8 19.5": ["huskiness"], "-4.9 16.0 0.1": ["aborad"], "7.5 -1.4 6.7": ["reannounced"], "10.7 11.3 8.7": ["mesoscopic"], "4.7 -1.3 10.7": ["carmen"], "12.8 16.2 28.6": ["picnicker"], "9.2 19.1 7.5": ["desuetude"], "1.2 5.9 10.8": ["hungarian"], "13.3 -2.2 -4.3": ["hmv"], "0.1 4.4 5.9": ["hymnlike"], "20.7 4.0 10.1": ["atomiser"], "4.7 15.5 4.0": ["autonomists"], "-2.5 7.1 12.3": ["anthocyanidins"], "6.3 8.7 23.0": ["cymbidiums"], "19.8 8.2 13.3": ["micromirrors"], "-0.9 2.0 6.5": ["fasciitis"], "10.2 1.1 9.7": ["anbd"], "2.4 20.1 7.5": ["charater"], "4.1 6.4 4.0": ["massification"], "-6.5 5.8 8.8": ["menstruated"], "12.1 9.4 13.7": ["junkmail"], "15.2 10.8 5.5": ["brower"], "12.8 32.4 13.2": ["stealthed"], "19.1 27.5 14.4": ["maleficent"], "11.0 11.7 8.2": ["bioscope"], "6.8 -0.5 1.2": ["amongthe"], "4.1 1.8 8.6": ["crosspoints"], "-0.6 5.8 2.1": ["vidofludimus"], "13.3 12.8 12.5": ["cheesefest"], "8.6 4.8 6.4": ["horologist"], "5.0 14.6 46.4": ["berley"], "4.6 22.5 11.3": ["knavery"], "16.1 3.9 7.1": ["delocalisation"], "9.7 13.3 32.5": ["punchbait"], "5.2 14.9 -7.6": ["rought"], "12.9 13.5 6.1": ["nosier"], "-2.3 10.6 16.5": ["inyo"], "1.3 20.3 -5.5": ["stregthen"], "8.2 9.3 3.6": ["contibute"], "10.5 0.9 -1.8": ["chatlines"], "3.4 9.9 3.3": ["againsts"], "0.8 -5.3 14.4": ["denturist"], "10.7 11.8 20.6": ["thermophiles"], "5.9 13.0 8.5": ["chhota"], "6.7 35.2 7.3": ["triangulator"], "5.5 10.9 17.9": ["sven"], "17.5 19.5 17.6": ["seracs"], "0.8 6.2 1.6": ["sondern"], "4.5 2.2 2.8": ["otology"], "4.9 14.6 14.4": ["husbandly"], "4.9 -1.0 4.0": ["prognosticates"], "13.8 10.9 20.3": ["nicker"], "8.3 17.4 9.7": ["sarc"], "4.1 17.3 8.5": ["nonissues"], "13.3 0.9 23.4": ["wheatgerm"], "-7.8 3.3 3.3": ["noa"], "6.7 6.5 10.3": ["littl"], "19.1 7.6 5.9": ["comsumption"], "10.0 10.0 17.5": ["refeed"], "2.1 -0.0 -3.3": ["permissioned"], "11.1 15.5 2.2": ["remans"], "10.2 14.3 2.6": ["sonde"], "13.0 4.3 19.2": ["dehors"], "1.0 6.0 0.2": ["nutured"], "3.0 -4.7 4.7": ["qd"], "-2.7 7.2 8.6": ["acetylcysteine"], "-1.1 21.7 8.5": ["nafs"], "-0.9 21.6 9.3": ["electorial"], "-3.6 -4.0 -2.9": ["epo"], "6.1 4.2 6.4": ["mastertone"], "2.1 1.0 -0.1": ["conservatoires"], "5.1 12.2 12.1": ["dormmates"], "-5.0 -2.1 2.3": ["ired"], "22.5 20.3 4.6": ["sloganeers"], "7.5 12.0 11.9": ["frugalista"], "7.6 14.0 2.8": ["kyosei"], "14.3 7.4 2.9": ["vectorization"], "-0.6 -0.4 4.4": ["hemiplegic"], "-2.8 19.9 9.8": ["budgetarily"], "2.5 -2.0 16.9": ["yiu"], "6.0 9.5 23.0": ["tradewind"], "4.4 11.1 6.1": ["itto"], "3.5 18.5 9.4": ["unpinned"], "3.3 14.7 7.0": ["sufferring"], "3.2 5.7 18.9": ["blueway"], "-5.8 28.6 -3.6": ["martyrdoms"], "5.6 5.1 20.0": ["eis"], "5.7 15.7 11.6": ["superposed"], "8.2 5.2 16.7": ["blockwork"], "0.9 11.9 -5.5": ["sayng"], "12.7 9.0 11.7": ["autostart"], "6.3 2.1 12.8": ["volksmarch"], "5.4 31.2 2.5": ["extremisms"], "15.3 5.1 37.7": ["dukkah"], "6.7 22.0 -1.9": ["intrests"], "-6.4 10.6 6.8": ["imporve"], "2.7 -4.2 2.9": ["chairholder"], "2.9 13.6 18.8": ["koban"], "20.3 6.6 23.1": ["lumberjacking"], "15.2 11.7 12.8": ["counterweighted"], "10.5 2.3 8.7": ["roadsigns"], "5.2 17.8 2.6": ["reconceptualize"], "8.4 8.1 11.2": ["roja"], "3.0 5.9 3.9": ["oems"], "12.8 2.2 17.4": ["glugged"], "-7.6 4.3 17.7": ["stelling"], "5.3 -3.8 6.2": ["teatro"], "-0.3 6.6 6.9": ["lightheavy"], "8.7 5.3 7.4": ["unactivated"], "-3.3 0.5 1.2": ["critcal"], "15.5 6.3 20.9": ["chickee"], "14.0 11.8 16.2": ["aeroponics"], "7.0 16.4 13.0": ["farse"], "11.0 16.5 18.3": ["frontierswoman"], "8.3 14.7 16.6": ["headshaking"], "0.0 4.9 9.4": ["fetuin"], "14.6 9.1 44.6": ["florentine"], "3.3 24.6 7.4": ["politcians"], "3.2 -1.6 1.9": ["deinstitutionalize"], "7.3 25.9 22.9": ["decoyed"], "6.6 10.8 26.4": ["forams"], "-6.7 -4.2 -1.5": ["agued"], "3.9 13.9 9.7": ["commandline"], "8.4 21.5 15.3": ["paraskevidekatriaphobia"], "8.6 7.7 14.3": ["hutton"], "18.9 12.0 16.2": ["sunloungers"], "18.2 10.5 32.1": ["orangy"], "13.8 1.2 6.1": ["shirtmaker"], "12.2 9.8 1.2": ["inrecent"], "10.2 4.4 -0.2": ["canagliflozin"], "2.4 11.9 12.4": ["residually"], "-2.5 4.5 5.4": ["colorectum"], "6.0 -3.3 6.4": ["centrale"], "3.6 1.1 12.5": ["shelby"], "-1.0 9.7 6.7": ["regularily"], "0.0 19.3 8.1": ["cryptosystem"], "6.7 6.6 14.5": ["nans"], "5.9 16.7 18.2": ["reattempt"], "2.5 16.5 13.5": ["anaerobes"], "2.0 -3.1 16.1": ["remelt"], "1.8 2.5 -9.9": ["membersof"], "9.9 13.3 12.6": ["dinginess"], "4.6 2.1 10.7": ["zak"], "-3.1 13.9 8.9": ["differen"], "1.9 3.8 15.3": ["noninsured"], "0.4 2.4 -10.0": ["agues"], "4.0 -4.3 0.5": ["finan"], "2.3 13.6 12.7": ["inflects"], "6.8 26.2 2.8": ["antihuman"], "2.6 1.8 6.6": ["sanjo"], "-1.7 5.9 23.5": ["orchardgrass"], "4.5 21.9 14.7": ["blighty"], "-1.1 8.3 -3.8": ["sensitizers"], "-0.8 8.5 9.5": ["unplatted"], "12.7 13.6 21.1": ["reroll"], "-0.5 12.9 3.7": ["expulsed"], "16.2 9.2 9.4": ["tossable"], "-11.3 11.2 1.5": ["benumbing"], "-4.5 10.7 3.6": ["rebleeding"], "4.4 -1.5 12.7": ["ctr"], "2.9 11.8 11.2": ["abnd"], "12.6 4.9 24.9": ["millefeuille"], "0.0 20.3 10.3": ["expendability"], "-13.7 6.4 10.6": ["saus"], "7.6 9.8 14.1": ["jazziest"], "15.8 12.3 50.3": ["silverside"], "4.1 3.4 11.6": ["grandparental"], "2.0 30.7 2.1": ["salafist"], "-5.0 5.7 10.9": ["carpooler"], "18.4 -4.9 12.4": ["percentto"], "14.9 4.5 11.9": ["svelter"], "16.3 15.0 13.0": ["whiniest"], "13.1 16.5 13.9": ["limbaugh", "rubio"], "4.7 5.7 14.8": ["midface"], "4.3 20.6 20.2": ["maenad"], "-7.7 5.3 0.6": ["npt"], "3.2 9.9 10.5": ["paro"], "5.6 7.5 7.2": ["uncontended"], "2.0 -3.2 8.8": ["cellarmaster"], "4.8 22.2 3.9": ["sackable"], "5.7 3.4 8.7": ["ells"], "3.3 0.4 8.9": ["antidiabetics"], "3.3 11.5 10.1": ["looksee"], "0.4 14.4 8.5": ["strided"], "-0.1 7.5 11.3": ["footbrake"], "6.0 2.5 1.3": ["cmte"], "19.6 16.4 16.0": ["acrophobic"], "16.9 9.2 29.0": ["beefburger"], "16.2 6.6 13.7": ["crackerjacks"], "16.6 16.8 5.8": ["nosiest"], "11.4 10.6 17.2": ["luxuriance"], "6.3 19.5 25.2": ["awns"], "12.1 -1.9 8.0": ["passerelle"], "0.2 13.7 6.6": ["ommissions"], "6.3 7.6 12.8": ["cinephilia"], "16.2 23.5 17.3": ["laowai"], "6.6 5.8 15.5": ["teus"], "6.0 5.6 3.8": ["unpicks"], "3.4 21.1 13.9": ["brushbacks"], "10.6 2.7 16.6": ["daa"], "5.5 3.1 10.8": ["cracky"], "2.0 6.4 2.8": ["thaat"], "7.6 8.4 18.8": ["megadroughts"], "17.9 11.4 4.2": ["transcosmos"], "14.1 -0.2 10.9": ["tollhouse"], "5.9 -3.6 7.3": ["methandienone"], "4.7 12.2 5.3": ["egresses"], "19.1 11.0 19.2": ["rugrat"], "12.3 13.8 21.5": ["legger"], "11.3 3.9 5.1": ["cuttingedge"], "8.0 15.2 9.7": ["ethinic"], "-5.4 7.5 1.7": ["nonqualifier"], "10.7 9.8 16.4": ["landbased"], "10.4 -1.7 4.7": ["nonelectronic"], "6.1 10.9 14.9": ["periorbital"], "4.4 -5.5 6.3": ["swabbings"], "4.6 11.1 10.8": ["heterogeneously"], "10.8 5.0 10.7": ["racerback"], "5.8 28.3 16.7": ["dogface"], "6.3 17.4 17.8": ["verruca"], "12.1 12.7 14.0": ["arcsecond"], "9.2 6.3 10.5": ["vieux"], "0.0 15.5 13.8": ["picknose"], "5.4 30.1 -6.9": ["atacks"], "1.0 -1.9 12.2": ["generico"], "3.0 17.7 4.7": ["highborn"], "13.7 5.4 20.7": ["evaporite"], "5.7 4.4 9.0": ["microcrystalline"], "16.8 11.6 20.9": ["pedicured"], "10.3 3.3 7.7": ["thousandsof"], "4.8 -5.5 3.5": ["partywear"], "-3.3 4.0 11.4": ["indult"], "-1.0 4.4 3.8": ["geomechanical"], "10.4 24.8 11.5": ["groundies"], "8.4 9.2 10.4": ["lipases"], "8.7 23.5 14.8": ["nutbars"], "17.9 8.2 36.6": ["eggwhite"], "10.2 4.3 18.7": ["strutters"], "-4.0 5.7 1.3": ["runscorers"], "-3.2 4.6 19.4": ["relocatees"], "16.0 4.5 20.7": ["cuphea"], "5.9 12.3 -7.8": ["securable"], "-5.1 11.8 12.3": ["weekers"], "7.9 -0.2 13.8": ["refinishers"], "10.0 7.6 1.9": ["electrolysers"], "11.2 9.4 2.6": ["restorationist"], "22.3 16.7 14.7": ["unscalable"], "5.0 7.3 5.4": ["readme"], "24.3 8.8 7.3": ["twistable"], "4.5 14.2 20.4": ["dethatching"], "-9.3 9.8 19.1": ["walay"], "0.5 1.3 3.2": ["challeng"], "0.2 5.3 2.6": ["encumbent"], "11.9 6.2 10.2": ["scsi"], "0.9 -0.1 4.2": ["communit"], "9.4 18.1 38.5": ["humuhumu"], "6.4 4.7 6.8": ["degazetted"], "8.7 14.3 1.4": ["sentimentalised"], "6.8 2.0 21.5": ["sherds"], "11.5 1.7 15.7": ["sprigged"], "5.4 24.6 2.9": ["habouring"], "7.3 -12.4 3.2": ["agreeed"], "15.4 15.5 9.3": ["supersuit"], "-0.6 6.0 6.9": ["microvolts"], "0.4 0.3 4.7": ["hypotonic"], "-9.4 8.6 -2.8": ["memoire"], "17.9 4.6 7.6": ["welched"], "6.1 5.3 1.8": ["vulcanizing"], "-5.2 5.3 8.6": ["dysautonomia"], "8.4 14.6 -2.2": ["solidfy"], "-2.8 -0.9 2.8": ["questi"], "-0.9 -5.6 3.1": ["nabumetone"], "8.6 11.8 2.4": ["tentage"], "6.1 8.7 2.1": ["registeredtrademarks"], "9.3 -3.9 11.0": ["unfurn"], "20.8 15.8 9.2": ["bushwhacker"], "3.1 -0.3 2.6": ["telepics"], "-3.3 6.0 2.4": ["actinide"], "6.0 10.7 12.5": ["ather"], "10.7 3.3 19.7": ["colby"], "4.4 2.6 10.2": ["laureateship"], "14.1 7.4 6.8": ["untuck"], "15.5 11.9 32.4": ["jalepeno"], "11.0 8.5 15.7": ["tremelo"], "4.5 13.8 5.1": ["birefringence"], "-1.3 7.5 11.1": ["tuloy"], "12.8 16.4 26.7": ["herp"], "9.2 8.0 40.2": ["sportboats"], "3.0 13.6 12.5": ["vechile"], "18.6 8.3 5.9": ["prepopulated"], "11.7 11.6 10.4": ["econom"], "-9.3 13.7 3.0": ["serostatus"], "7.2 15.8 23.0": ["culturalist"], "14.4 15.7 12.5": ["wavey"], "-0.5 6.4 12.1": ["tujhe"], "30.4 3.4 15.3": ["thebiggest"], "12.2 4.7 1.0": ["oppotunities"], "-5.8 11.0 1.0": ["missings"], "-1.1 3.8 4.0": ["triac"], "17.9 15.6 18.2": ["bollock"], "10.4 6.5 0.9": ["prototypic"], "-1.9 27.4 3.0": ["adjutants"], "-1.2 13.8 6.9": ["supersaturation"], "25.7 19.2 12.6": ["minifig"], "19.3 5.3 1.1": ["propietary"], "5.6 8.6 10.1": ["radiohead"], "11.2 5.0 10.4": ["doorsills"], "8.9 -5.0 6.0": ["rehosting"], "15.3 36.4 18.6": ["spellcasting"], "4.8 10.0 11.2": ["reappropriating"], "8.5 -1.3 6.1": ["plu"], "-0.0 24.9 4.5": ["overcomers"], "-2.6 12.9 10.8": ["matriptase"], "19.8 22.4 -2.1": ["cyberattackers"], "6.4 7.6 12.7": ["neng"], "5.2 31.2 14.6": ["wheresoever"], "22.3 14.0 10.1": ["mundanities"], "11.9 -2.8 -1.4": ["homewear"], "15.6 5.1 33.1": ["sundried"], "10.5 6.2 21.3": ["hanji"], "-1.4 4.2 -2.4": ["crystallographer"], "18.5 10.5 13.6": ["breezeblock"], "3.7 4.8 8.1": ["availablility"], "12.9 7.9 15.9": ["peregrination"], "7.5 -0.5 11.5": ["transglutaminase"], "8.4 30.2 0.3": ["thoughtcrime"], "11.1 -12.3 -6.3": ["ollowing"], "0.9 -0.4 4.5": ["azo"], "4.5 11.6 -0.7": ["concerting"], "17.7 -1.8 10.9": ["agriculturals"], "0.9 3.9 -1.2": ["chromatographers"], "10.2 5.4 29.5": ["precooking"], "3.9 6.2 11.5": ["salsero"], "8.3 23.6 10.6": ["militance"], "13.7 9.4 13.5": ["backplates"], "9.2 24.3 0.6": ["chimurenga"], "-3.4 8.5 4.5": ["clomipramine"], "1.8 22.1 4.0": ["personnell"], "7.9 5.4 8.1": ["superflyweight"], "8.1 3.7 31.3": ["kueh"], "5.8 8.0 2.4": ["orm"], "9.9 1.2 22.7": ["zhu"], "4.6 6.5 2.7": ["bzw"], "6.1 11.6 7.2": ["anaesthetising"], "7.7 2.5 8.5": ["sportstar"], "8.9 -3.8 -4.2": ["commisions"], "0.2 9.7 11.0": ["cummings"], "10.0 12.6 24.5": ["banderillas"], "-1.5 11.0 13.1": ["sinasabi"], "1.9 5.0 -2.7": ["microbolometer"], "-3.6 6.7 5.4": ["ection"], "5.7 15.9 7.1": ["visualist"], "-1.3 0.2 16.1": ["marami"], "8.1 -2.8 14.1": ["lps"], "19.9 7.5 19.3": ["glugs"], "11.8 1.2 16.6": ["funkin"], "9.4 14.7 10.8": ["unmetabolized"], "1.9 5.0 15.9": ["pregunta"], "-1.6 6.3 11.6": ["classpath"], "8.5 17.6 18.8": ["asswipe"], "2.0 17.3 7.3": ["negritude"], "10.9 11.9 9.9": ["fanastic"], "11.3 18.6 20.0": ["withs"], "1.8 11.4 0.3": ["inhalational"], "13.5 9.0 11.9": ["femcee"], "12.3 6.4 34.7": ["kakariki"], "12.4 5.3 7.8": ["paseos"], "3.9 13.4 8.4": ["hyperexcitability"], "14.5 3.2 11.6": ["lappies"], "-1.0 6.6 3.5": ["scatterometry"], "-0.3 6.1 15.1": ["winback"], "5.7 3.3 7.8": ["gobierno"], "1.6 -3.8 12.4": ["canadien"], "2.3 8.5 3.6": ["prerecord"], "12.0 16.7 20.0": ["protocells"], "11.1 3.4 11.5": ["entenders"], "4.3 5.3 10.6": ["vrai"], "0.3 13.7 9.2": ["ancestrally"], "1.0 1.3 -7.1": ["earleir"], "10.0 20.7 17.1": ["wuv"], "7.0 18.5 3.9": ["domo"], "18.7 4.5 2.1": ["beneficiating"], "9.6 15.2 6.7": ["glucans"], "-2.1 12.2 3.5": ["padayatras"], "0.4 2.6 6.7": ["aao"], "10.0 -1.6 21.9": ["shak"], "9.2 3.5 8.1": ["whelped"], "10.4 4.9 2.0": ["kingmaking"], "9.7 10.2 22.7": ["gamefowl"], "18.9 13.3 9.8": ["slogfest"], "6.9 4.3 13.5": ["precompetitive"], "-6.3 6.4 2.5": ["mediastinitis"], "1.0 8.5 3.6": ["songtitles"], "6.0 3.6 7.2": ["recordsetting"], "6.7 0.2 9.3": ["westminster"], "10.7 8.6 13.5": ["mbanje"], "1.2 -7.0 5.3": ["lllinois"], "6.5 31.8 10.5": ["reforging"], "12.4 8.0 4.2": ["photoblogging"], "7.0 12.2 19.1": ["coevolved"], "18.4 12.4 21.4": ["blubbers"], "0.7 -6.9 11.3": ["denturists"], "-0.1 9.6 0.6": ["polysomnogram"], "9.1 0.1 9.3": ["desmin"], "12.0 9.9 8.6": ["landbase"], "8.3 12.0 7.2": ["upraising"], "10.5 7.6 29.4": ["squabs"], "-4.2 6.9 13.4": ["recopied"], "-4.6 3.1 7.4": ["householding"], "-0.2 3.5 -3.7": ["oach"], "4.5 12.6 9.2": ["nononsense"], "12.6 21.3 8.9": ["sanctums"], "19.6 14.7 21.1": ["whatta"], "15.0 23.7 7.1": ["triadic"], "-1.6 2.4 7.6": ["polyglutamine"], "7.5 9.3 6.0": ["unobtrusiveness"], "7.9 12.4 9.9": ["reachers"], "3.1 9.4 18.4": ["bhar"], "24.8 6.7 0.7": ["manufacturered"], "9.9 10.5 2.8": ["theatened"], "1.1 7.8 2.8": ["borned"], "4.8 18.6 1.4": ["askari"], "12.2 35.2 7.3": ["cyberweapons"], "1.0 6.7 8.5": ["deprovisioning"], "14.4 19.1 11.8": ["tukuls"], "14.6 31.4 9.6": ["sigil"], "13.9 15.4 36.5": ["barbels"], "7.7 4.7 23.8": ["planaria"], "12.3 12.0 9.6": ["uncurbed"], "-3.3 6.1 14.3": ["wahi"], "2.8 5.0 5.5": ["longwave"], "2.4 15.4 1.0": ["denunciatory"], "2.8 7.6 2.6": ["newsbreak"], "1.2 7.5 16.2": ["kyogen"], "5.8 6.8 4.9": ["fuction"], "12.9 15.6 10.9": ["tarrying"], "3.1 5.6 2.6": ["nonobviousness"], "11.3 16.7 17.7": ["lurgy"], "11.1 9.6 2.5": ["undisputably"], "13.5 2.9 20.2": ["ulus"], "8.9 15.8 22.5": ["microbials"], "10.1 10.1 8.9": ["superconferences"], "10.6 5.5 19.8": ["laguna"], "11.8 9.4 15.6": ["quarterpanel"], "10.1 9.8 6.2": ["offroaders"], "7.0 6.6 8.5": ["schoolmarms"], "2.9 9.4 10.2": ["ghostbar"], "3.5 20.6 7.8": ["trinitarian"], "-4.1 18.1 4.1": ["carcade"], "22.7 9.4 16.1": ["savvily"], "7.8 5.5 10.9": ["maak"], "20.6 19.0 10.2": ["buttheads"], "6.2 12.0 15.5": ["rabs"], "0.5 16.5 2.0": ["relize"], "6.2 5.3 6.2": ["parece"], "14.2 13.5 9.8": ["undetailed"], "2.2 3.9 17.9": ["oxalates"], "0.4 16.7 8.9": ["serosorting"], "5.9 15.4 13.5": ["larrikinism"], "10.1 4.4 13.3": ["doming"], "15.7 22.5 21.0": ["recolonised"], "14.4 14.4 10.9": ["exaflood"], "-7.0 3.2 6.6": ["volun"], "-14.1 13.6 11.9": ["nonpharmacologic"], "7.8 4.6 17.3": ["proteinaceous"], "-2.2 11.9 -3.8": ["reputability"], "7.1 3.1 5.4": ["fnal"], "3.0 13.5 2.2": ["bitterlemons"], "2.8 14.3 9.1": ["helibase"], "-1.5 26.1 11.7": ["sargent"], "4.5 8.4 3.6": ["rotables"], "7.6 -5.5 -6.1": ["announc"], "4.3 12.3 9.7": ["omiru"], "-9.0 8.8 -6.6": ["outstand"], "17.2 12.9 -3.6": ["uconnect"], "5.5 25.5 6.3": ["airsickness"], "9.8 8.6 3.7": ["unoperational"], "-2.4 2.2 8.1": ["sulfonamide"], "20.7 3.7 16.1": ["helixes"], "6.7 13.2 4.9": ["nanoworms"], "14.7 25.3 13.7": ["trecherous"], "17.5 17.8 5.1": ["speading"], "1.1 7.4 10.0": ["jl"], "11.8 3.7 41.4": ["porcinis"], "8.2 16.1 19.9": ["lames"], "6.5 8.0 15.1": ["pagdi"], "8.1 10.2 7.6": ["goalkeep"], "5.1 12.4 12.4": ["multilateralisation"], "7.4 15.8 12.0": ["ungenuine"], "8.6 6.4 6.9": ["mesure"], "5.0 10.6 -0.1": ["wirefree"], "0.8 9.6 7.1": ["astrophotographer"], "7.9 4.9 9.6": ["forn"], "2.0 7.4 3.9": ["bibliometric"], "16.6 27.2 7.1": ["planespotters"], "4.2 4.2 15.8": ["minisode"], "22.2 -1.5 25.6": ["skyr"], "3.1 11.6 10.8": ["daladala"], "12.8 19.4 19.2": ["jungled"], "8.8 16.1 7.5": ["viceversa"], "3.4 24.5 6.8": ["traumatises"], "11.2 18.5 -1.3": ["fawningly"], "18.1 22.6 10.9": ["globalizers"], "-2.0 6.9 10.8": ["mehadrin"], "2.8 21.2 9.7": ["equilibriums"], "9.9 8.7 9.8": ["senors"], "17.1 9.3 8.2": ["aficianados"], "12.1 -1.2 21.5": ["snarfed"], "12.1 10.6 14.0": ["mudded"], "6.5 10.7 0.5": ["flightsim"], "9.4 11.6 8.1": ["linksy"], "4.0 15.8 15.5": ["fastballer"], "9.5 9.4 35.0": ["meatloaves"], "-1.1 29.3 4.0": ["overpassed"], "2.0 11.9 14.1": ["mabe"], "-1.0 2.6 3.8": ["wisenheimers"], "-0.2 7.6 13.7": ["goddaughters"], "5.3 -3.8 8.3": ["segunda"], "9.6 21.1 2.5": ["responsibily"], "7.3 6.9 19.6": ["sige"], "7.9 12.4 23.3": ["hyde"], "8.0 1.5 3.2": ["funtion"], "5.8 7.3 4.8": ["uncreditworthy"], "2.6 -4.4 -1.3": ["clu"], "16.7 10.7 11.9": ["affordances"], "10.7 -2.3 6.9": ["labellers"], "11.3 6.3 16.7": ["ashed"], "17.7 22.6 15.3": ["soundwave"], "-1.0 4.9 5.5": ["tweeked"], "7.0 4.4 16.1": ["pyroclastics"], "6.0 12.5 11.2": ["amphibolites"], "11.9 28.1 8.2": ["papists"], "12.5 3.4 7.8": ["cryocooler"], "25.7 19.7 22.3": ["beaky"], "-0.3 17.0 13.4": ["unrelatable"], "1.3 8.3 5.9": ["overset"], "1.2 12.6 2.7": ["longetivity"], "7.8 7.3 25.9": ["stemmy"], "-13.2 8.4 7.0": ["aske"], "7.9 12.7 2.3": ["jubiliation"], "-5.0 -0.5 -2.7": ["evaulation"], "9.9 7.4 26.7": ["fraser"], "2.0 10.4 10.3": ["ourbusiness"], "-1.8 8.5 9.7": ["overdosage"], "-6.3 -1.4 6.4": ["informalities"], "-7.6 9.4 9.4": ["failovers"], "1.5 9.3 19.1": ["wive"], "5.7 3.0 13.3": ["interlayered"], "10.7 10.2 26.4": ["chordates"], "10.3 22.2 7.0": ["bloodthirst"], "0.2 12.3 7.2": ["overdeveloping"], "-1.4 18.7 6.0": ["underthrows"], "-4.6 1.5 -8.4": ["memberof"], "-3.9 10.0 1.2": ["khula"], "14.3 12.2 11.4": ["nemo"], "11.7 6.7 8.2": ["inflammed"], "17.5 11.6 11.1": ["menora"], "4.8 3.8 3.3": ["vicory"], "0.2 5.7 3.8": ["dermatoses"], "-0.5 8.2 5.8": ["aggrievement"], "5.6 19.4 2.6": ["attrocious"], "-7.7 16.8 -2.6": ["exprience"], "9.5 18.5 17.8": ["subtley"], "17.4 14.6 0.9": ["catapaulted"], "8.1 6.8 12.9": ["kuduro"], "8.1 -8.3 18.4": ["hfr"], "22.2 11.0 37.5": ["chough"], "6.5 24.0 11.9": ["uptightness"], "-1.4 15.4 -0.7": ["memoires"], "2.8 6.0 -1.0": ["helicases"], "-4.8 4.6 11.4": ["dring"], "18.8 3.3 16.2": ["goldman"], "-1.5 2.9 4.6": ["drivng"], "21.8 17.3 25.7": ["redbird"], "4.5 31.8 -2.1": ["atttack"], "-2.6 10.3 12.5": ["swearings"], "8.9 16.8 9.3": ["earmarker"], "9.8 -1.9 13.0": ["topstitching"], "3.6 2.1 13.5": ["metromix"], "5.7 14.0 13.2": ["landsliding"], "2.4 2.5 10.8": ["dimethicone"], "14.3 5.0 33.7": ["wagtails"], "16.2 15.4 12.6": ["banjaxed"], "10.7 10.3 11.4": ["lutely"], "6.4 10.1 9.9": ["gaana"], "7.9 11.2 10.6": ["fulling"], "10.5 12.3 16.8": ["gabbled"], "2.4 -2.6 4.2": ["chloralkali"], "1.1 13.6 28.2": ["kapu"], "5.2 7.7 1.4": ["dynamicsoft"], "-6.6 3.6 6.9": ["thirdbaseman"], "14.1 12.6 9.3": ["formin"], "-0.5 9.2 0.2": ["valorise"], "4.9 -3.5 16.3": ["nextyear"], "4.8 9.0 7.0": ["grosse"], "5.9 16.9 6.0": ["handcrews"], "8.9 22.3 7.4": ["blamelessness"], "13.0 -4.8 -5.1": ["heaquarters"], "7.8 13.4 16.1": ["unwalkable"], "25.0 24.1 20.9": ["stickmen"], "7.5 17.6 8.4": ["anthropic"], "-4.0 10.2 24.5": ["lampricide"], "8.9 6.1 2.0": ["numbe"], "7.6 15.5 10.5": ["typological"], "3.4 22.8 -2.0": ["mancrush"], "13.6 8.4 -2.6": ["particualrly"], "4.6 0.6 37.0": ["crimini"], "1.4 13.2 15.9": ["exhalite"], "12.0 15.2 10.3": ["superheroines"], "2.7 9.1 7.5": ["ipsw"], "21.0 10.0 9.2": ["mergence"], "3.2 11.1 10.6": ["dejavu"], "7.3 8.1 7.9": ["ittle"], "7.9 21.2 7.9": ["comicdom"], "2.4 5.6 -1.1": ["programms"], "19.3 11.3 19.3": ["koma"], "13.5 15.9 33.7": ["ridgeback"], "-5.2 -6.7 -2.4": ["receiv"], "10.1 4.6 20.9": ["crocheter"], "14.3 4.3 19.8": ["sippy"], "9.7 13.8 15.5": ["midwesterners"], "12.0 7.6 6.7": ["retroreflective"], "8.8 24.9 6.9": ["backbite"], "-4.5 -1.7 7.8": ["chemin"], "16.3 23.8 13.3": ["vulgarians"], "2.2 -7.2 12.0": ["fono"], "-3.0 -0.9 8.9": ["utilisations"], "1.1 7.7 0.9": ["readopting"], "-0.9 5.0 12.3": ["unreplaced"], "-7.3 10.0 10.5": ["waivering"], "12.1 17.1 18.5": ["sponginess"], "6.9 4.4 25.5": ["midthigh"], "10.6 7.4 1.2": ["silverscreen"], "-3.3 9.1 3.5": ["hypothesises"], "2.4 6.7 9.2": ["subpotent"], "7.0 2.9 8.0": ["gearmotor"], "-1.3 2.0 3.1": ["photoprotection"], "9.3 8.0 22.0": ["patas"], "-1.3 11.9 6.2": ["injur"], "8.7 -2.2 4.5": ["uper"], "12.3 25.3 11.5": ["unrooted"], "10.3 15.4 13.0": ["shlocky"], "7.4 12.4 5.1": ["environement"], "7.7 1.1 22.8": ["stromatolite"], "7.2 7.1 6.5": ["nongay"], "2.7 13.6 12.0": ["cloy"], "-6.3 7.2 7.7": ["endoleaks"], "11.6 4.9 12.2": ["trophoblast"], "2.0 3.5 10.6": ["sotto"], "13.4 24.7 11.7": ["exploder"], "11.7 15.7 15.8": ["rousts"], "2.5 8.6 33.1": ["pfiesteria"], "1.7 2.4 13.0": ["muxponder"], "12.4 30.3 10.5": ["inalterable"], "5.6 10.0 3.4": ["svg"], "4.9 3.6 -1.9": ["structurers"], "20.9 26.7 17.6": ["telekinetically"], "3.8 6.2 16.7": ["amah"], "3.1 8.0 2.5": ["thegroup"], "8.8 0.0 9.0": ["concepted"], "23.9 9.0 19.5": ["weatherworn"], "3.9 16.3 6.6": ["wim"], "8.7 9.6 16.3": ["bordetella"], "16.8 9.1 9.1": ["collywobbles"], "12.3 4.2 8.5": ["gass"], "-4.9 11.7 15.0": ["drouth"], "3.9 5.5 8.9": ["andtwo"], "15.5 -1.7 10.7": ["arket"], "11.5 11.6 4.6": ["nanofactory"], "17.1 -1.3 5.7": ["infancies"], "7.3 -4.2 7.7": ["ibs"], "18.9 -6.3 11.9": ["paypackets"], "7.8 9.7 17.2": ["acutal"], "10.9 17.2 8.9": ["tsotsis"], "10.8 18.0 11.2": ["concussing"], "8.4 7.1 9.9": ["multichannels"], "-1.7 11.4 2.7": ["hakim"], "8.6 24.8 18.7": ["pantywaists"], "1.8 19.0 6.3": ["constitutionalize"], "4.3 10.1 13.6": ["nain"], "9.9 5.9 9.3": ["microcephalin"], "3.2 5.5 13.4": ["apan"], "17.1 14.9 27.3": ["coati"], "0.8 8.2 8.2": ["midlist"], "7.7 3.5 21.0": ["prandial"], "23.0 -3.0 16.1": ["kitchenwares"], "-4.5 16.6 10.7": ["vaginismus"], "10.3 17.6 22.8": ["pugmark"], "6.1 14.2 8.1": ["plectasin"], "1.8 19.6 9.9": ["cytotoxin"], "5.7 11.9 6.8": ["whne"], "2.5 11.9 -0.6": ["meddlesomeness"], "18.5 6.4 22.2": ["stockinged"], "6.5 15.6 15.8": ["shizz"], "-2.8 12.4 -1.5": ["assistence"], "10.9 12.4 13.7": ["euthanising"], "-3.3 12.2 9.6": ["thigns"], "22.8 16.3 16.8": ["whoopsie"], "15.5 14.6 30.3": ["topsail"], "4.8 -2.6 5.3": ["angsting"], "0.6 19.1 7.3": ["unfulfillment"], "10.6 -0.2 -3.1": ["suported"], "11.6 19.9 14.6": ["themslves"], "-5.2 19.3 5.2": ["diametrical"], "3.9 13.0 9.5": ["goli"], "15.9 11.5 12.6": ["streetcorners"], "3.1 -2.5 1.4": ["lih"], "12.4 10.2 10.0": ["funster"], "11.7 18.3 12.6": ["shiznit"], "-1.4 10.8 8.4": ["accompli"], "6.3 -0.2 6.9": ["microcellular"], "8.2 20.1 19.6": ["recriminatory"], "16.7 0.4 14.1": ["scratchie"], "-2.7 5.0 7.0": ["hyperammonemia"], "4.7 29.5 21.7": ["solitarily"], "9.8 8.5 14.3": ["ilium"], "10.1 4.6 9.5": ["boyshorts"], "6.8 24.1 5.6": ["biothreats"], "6.1 11.8 17.3": ["inta"], "8.9 16.5 15.2": ["muthafucka"], "-0.7 -5.1 7.0": ["prekindergartners"], "11.7 -1.6 -5.3": ["itraffic"], "14.2 8.5 18.0": ["nymphets"], "-2.9 1.6 14.3": ["meno"], "16.4 22.3 18.2": ["masklike"], "8.4 5.6 11.8": ["bubbliness"], "4.8 4.4 6.9": ["darbuka"], "-4.7 -1.8 1.5": ["clavulanate"], "11.7 13.2 19.6": ["impalings"], "-4.3 3.0 1.0": ["downconverters"], "3.4 10.9 10.5": ["aldo"], "6.5 5.3 5.2": ["officiel"], "7.7 10.5 2.6": ["multiradio"], "3.1 5.0 6.7": ["aai"], "9.3 8.6 14.8": ["alleyoop"], "-0.7 8.7 13.6": ["stewardships"], "10.7 3.5 6.7": ["txts"], "4.1 11.7 -0.3": ["organsations"], "9.2 8.4 15.2": ["bargirl"], "6.1 10.3 26.3": ["mezza"], "7.6 7.3 10.1": ["lightwave"], "8.5 -5.4 10.8": ["weighlifting"], "15.7 12.3 12.0": ["reinflating"], "20.2 18.9 13.5": ["invincibly"], "16.7 2.7 12.5": ["scribbly"], "10.6 21.2 15.0": ["khukuri"], "8.4 10.5 5.4": ["anot", "dinitrogen"], "1.5 6.3 -2.8": ["theprocess"], "12.2 1.0 -3.1": ["wunderkid"], "11.0 13.1 12.7": ["esoterically"], "3.5 5.1 14.1": ["highsticking"], "5.0 16.6 21.5": ["coquis"], "1.4 1.6 5.3": ["nonaccruing"], "4.7 11.6 -2.3": ["deparments"], "-6.7 5.0 2.1": ["captaincies"], "0.4 -0.2 15.2": ["ecotoxicologist"], "6.8 23.3 6.6": ["idealising"], "0.1 6.4 0.5": ["theon"], "-9.8 2.5 1.0": ["posttransplant"], "10.4 1.9 21.3": ["tallboys"], "10.8 -6.0 1.6": ["promiment"], "1.3 1.4 5.2": ["microstepping"], "-3.5 7.9 15.6": ["hata"], "18.3 7.4 31.8": ["sandspit"], "5.6 -0.3 2.8": ["accesso"], "-3.8 14.8 4.3": ["speechmakers"], "11.1 6.4 7.1": ["grungey"], "6.2 7.9 0.7": ["gossipmonger"], "10.4 19.2 18.5": ["caniscandida"], "16.3 18.6 9.5": ["thuggishly"], "8.5 35.0 18.5": ["rambo"], "4.9 19.4 12.6": ["habitus"], "10.7 -3.1 -3.0": ["inclusing"], "-1.9 4.1 9.3": ["osteogenesis"], "9.1 14.6 4.9": ["martials"], "6.2 13.8 8.9": ["blesseds"], "3.8 7.5 8.4": ["roomer"], "7.0 1.2 12.8": ["veda"], "15.8 5.5 4.9": ["conflux"], "0.5 10.1 6.7": ["immunoregulatory"], "3.9 10.6 7.2": ["multicellularity"], "-7.9 -2.3 1.5": ["vasoactive"], "15.8 15.3 10.5": ["apparati"], "1.8 8.5 6.5": ["champerty"], "1.5 0.0 11.5": ["hied"], "4.4 11.7 1.5": ["narcoanalysis"], "19.2 -2.5 29.8": ["crispies"], "8.4 17.0 -0.7": ["challeges"], "10.1 2.4 13.6": ["sixtysomethings"], "6.0 -12.6 4.6": ["announ"], "9.0 8.3 21.1": ["popo"], "6.6 1.7 24.5": ["murg"], "17.0 -2.4 2.6": ["architectured"], "3.9 4.0 11.2": ["geogrid"], "5.3 4.6 6.3": ["miglustat"], "-3.4 7.5 9.8": ["fpgas"], "1.1 7.5 8.4": ["brucella"], "8.0 9.6 8.9": ["synchromesh"], "10.1 20.5 11.2": ["hellaciously"], "-4.5 7.9 1.7": ["peroid"], "-3.6 16.7 4.2": ["exoteric"], "-2.0 2.2 13.4": ["greenup"], "-3.1 1.5 3.9": ["levalbuterol"], "10.6 13.9 12.6": ["foresake"], "10.7 7.3 18.1": ["burghs"], "13.4 20.3 22.1": ["exoticness"], "14.7 17.0 13.3": ["airbrakes"], "8.6 5.2 8.6": ["ticketbuyers"], "5.3 0.0 -2.0": ["softcopy"], "6.2 -0.1 3.9": ["deinking"], "10.3 -9.0 12.3": ["ente"], "19.4 1.6 12.6": ["elasticised"], "11.3 5.3 17.1": ["mangabeys"], "1.9 -3.1 12.5": ["yale"], "-1.4 9.6 7.2": ["listenability"], "-5.5 -8.6 5.9": ["highschools"], "-5.5 2.2 -1.2": ["hospitalwide"], "10.7 7.2 1.7": ["ofher"], "14.5 22.2 15.5": ["sayer"], "14.0 7.3 7.6": ["schlump"], "1.3 8.9 15.8": ["gori"], "-3.0 17.2 -3.1": ["neigboring"], "3.5 4.4 9.2": ["xps"], "10.7 7.0 23.1": ["jumpier"], "9.4 3.9 12.1": ["trackie"], "13.0 10.8 21.3": ["gentians"], "11.3 21.7 15.0": ["eyeroll"], "2.9 -4.1 10.0": ["trichologist"], "12.9 3.6 5.0": ["ghg"], "5.8 17.2 9.4": ["googolplex"], "10.9 9.5 15.9": ["vogueing"], "16.1 16.6 13.7": ["suplexing"], "7.2 3.3 12.3": ["rulebreakers"], "10.8 10.5 19.3": ["countersink"], "7.1 12.0 5.8": ["uncertainities"], "5.8 18.2 1.8": ["precess"], "8.8 0.7 14.3": ["desalter"], "-13.8 -0.9 13.1": ["nonrelative"], "11.9 7.2 14.1": ["catgut"], "7.1 4.5 17.2": ["procollagen"], "3.9 6.3 -2.7": ["flexfuel"], "1.7 0.9 5.8": ["mova"], "3.7 5.4 4.5": ["thisrelease"], "8.4 1.0 12.3": ["rustproofing"], "26.2 20.5 23.2": ["gryphon"], "4.9 20.9 8.8": ["symbolization"], "2.0 7.1 7.6": ["procrastinations"], "6.1 13.8 16.7": ["khali"], "13.4 11.6 11.7": ["scriveners"], "13.4 6.2 6.4": ["fantastique"], "17.8 6.9 22.1": ["clacker"], "14.5 6.0 39.8": ["pinenuts"], "2.2 7.9 7.5": ["arithmetics"], "15.0 8.3 17.4": ["sunseed"], "-1.8 12.3 -2.5": ["unitarian"], "4.0 -1.0 0.0": ["milrinone"], "23.3 16.2 16.7": ["catapault"], "-0.2 12.2 2.7": ["reopposing"], "4.6 11.3 8.1": ["remelted"], "2.2 3.3 14.9": ["chainless"], "1.5 16.3 4.1": ["electroshocks"], "-0.1 9.2 -0.9": ["leikai"], "2.2 12.8 15.3": ["broodiness"], "6.8 -1.5 14.0": ["snootier"], "9.6 6.2 18.8": ["herpetological"], "4.2 11.2 20.5": ["unsampled"], "2.6 7.2 7.9": ["cuenta"], "11.3 5.7 2.2": ["staled"], "5.9 8.7 17.7": ["steepler"], "17.9 20.8 28.6": ["hunkers"], "4.9 12.8 14.6": ["clawhammer"], "10.2 7.1 5.6": ["flatshare"], "2.5 14.0 9.4": ["wheals"], "6.0 4.5 14.6": ["boone"], "23.1 16.1 8.2": ["entombs"], "16.6 14.3 23.6": ["hibachis"], "6.1 3.0 7.2": ["flac"], "0.6 7.8 18.2": ["enrofloxacin"], "9.9 20.9 11.6": ["everybodies"], "6.9 21.9 9.4": ["checkmates"], "-0.5 -2.1 2.9": ["iknow"], "9.6 -0.7 14.3": ["toolless"], "-1.2 4.7 6.6": ["ajudged"], "6.0 18.3 9.9": ["statesperson"], "15.4 4.7 6.2": ["foamer"], "13.0 19.0 19.4": ["catamounts"], "2.9 15.3 8.6": ["mwalberg"], "3.5 -0.7 5.0": ["outdelivered"], "6.7 14.1 7.7": ["sclaffed"], "-4.0 27.9 6.7": ["opponets"], "0.7 5.0 12.6": ["annuitisation"], "9.4 12.3 -4.2": ["asnd"], "17.2 17.5 15.5": ["thunked"], "16.9 11.4 14.5": ["vomitorium"], "6.3 12.0 9.0": ["fadeouts"], "2.0 -0.7 33.3": ["toor"], "2.5 9.2 2.0": ["likers"], "17.4 16.5 4.1": ["pwns"], "5.0 25.2 6.5": ["concience"], "-5.7 8.1 11.0": ["orchitis"], "4.6 19.4 10.6": ["yourselfs"], "4.7 1.6 2.5": ["emf"], "6.7 -7.5 1.1": ["kz"], "4.7 4.2 -1.7": ["unblushing"], "17.8 4.7 11.5": ["thown"], "2.7 -7.0 5.6": ["analyis"], "6.9 22.6 14.7": ["remerge"], "1.3 6.6 5.4": ["kamu"], "4.4 20.8 -3.5": ["tawhid"], "-7.9 4.1 1.5": ["dramaturgs"], "-14.4 9.6 6.7": ["talmid"], "2.0 12.5 16.6": ["yippie"], "-10.4 0.4 6.6": ["nator"], "3.3 17.2 16.1": ["excrescences"], "18.2 9.6 18.4": ["castanet"], "18.8 15.5 18.0": ["navvies"], "10.1 5.0 1.8": ["prestigiously"], "-4.9 8.7 11.8": ["atbats"], "-0.7 -1.4 5.3": ["psychometricians"], "10.3 9.7 5.9": ["inovative"], "9.4 13.5 15.0": ["intraclub"], "7.7 5.9 5.6": ["ambi"], "4.4 6.4 18.7": ["braider"], "6.1 30.4 9.7": ["graymail"], "3.2 4.2 6.5": ["cles"], "13.7 10.1 16.6": ["scooch"], "-0.1 14.8 11.4": ["overcoaching"], "2.9 5.8 11.3": ["microarchitectures"], "19.1 8.4 5.4": ["applicances"], "-2.6 4.8 1.7": ["phototoxicity"], "14.5 8.7 8.9": ["cockup"], "-6.7 7.1 7.2": ["thyroglobulin"], "9.8 9.2 7.8": ["polyketide"], "12.3 15.7 8.5": ["jargony"], "10.0 11.2 9.4": ["profitabilty"], "17.8 9.9 11.4": ["refurbed"], "1.2 1.5 2.3": ["optimisitic"], "9.4 9.1 7.4": ["multiferroic"], "0.4 11.5 21.2": ["flatwoods"], "6.3 4.4 26.1": ["oilmeal"], "21.9 6.2 16.2": ["dolmen"], "14.0 8.5 14.9": ["blinkin"], "17.4 4.7 15.2": ["welting"], "-3.3 8.2 0.8": ["ballotting"], "19.8 0.7 29.8": ["shagreen"], "6.0 -5.0 27.4": ["entres"], "0.2 8.1 7.2": ["maximun"], "1.9 16.3 2.0": ["thoughs"], "0.4 13.2 4.8": ["penetrant"], "10.6 23.0 7.5": ["ambuscade"], "9.5 24.9 16.2": ["ninjitsu"], "6.1 11.7 9.8": ["effert"], "7.2 -2.8 5.4": ["alison"], "-4.3 14.8 -3.6": ["civilianisation"], "-7.0 2.5 11.0": ["moni"], "15.7 15.5 8.5": ["nightclubber"], "15.8 8.3 30.3": ["napoleons"], "4.2 13.9 7.6": ["spoilerish"], "3.7 -4.0 5.9": ["aif"], "-9.7 9.8 4.3": ["redetermine"], "14.3 17.9 15.8": ["nocturnally"], "10.7 7.5 16.2": ["fila"], "17.6 14.0 3.8": ["unshackles"], "12.1 3.7 13.7": ["tyremakers"], "12.6 13.6 -2.2": ["admiting"], "11.2 6.8 17.5": ["waspy"], "6.8 -3.1 5.8": ["espace"], "15.3 18.3 28.3": ["waxwing"], "1.4 10.7 0.6": ["valueable"], "3.0 8.9 7.2": ["diarrohea"], "13.6 2.3 28.9": ["noisette"], "9.1 -2.4 14.4": ["asssets"], "22.7 15.3 3.8": ["astroturfers"], "-0.4 4.8 14.2": ["underearn"], "-0.1 6.1 14.4": ["marx"], "8.8 7.7 10.5": ["pervasion"], "5.2 4.6 8.3": ["chitchatted"], "0.7 15.4 9.3": ["utilitarians"], "16.8 11.5 36.9": ["butanding"], "-3.7 30.0 0.6": ["scarifies"], "1.5 8.2 1.7": ["socialmedian"], "-6.5 4.1 9.8": ["autocorrelation"], "-4.3 11.8 11.2": ["idarubicin"], "2.2 9.5 7.1": ["datatype"], "4.9 19.0 13.3": ["jaya"], "14.0 5.3 11.5": ["dwon"], "6.5 13.3 10.9": ["standed"], "-3.6 -4.9 2.7": ["complimentaries"], "7.5 14.5 6.4": ["overcounting"], "3.7 9.0 4.4": ["fieldbuses"], "15.6 15.1 20.7": ["knifelike"], "1.2 7.1 9.6": ["aana"], "19.6 16.9 12.4": ["microrobot"], "8.4 24.7 8.5": ["exageration"], "12.8 13.5 13.3": ["doli"], "13.0 12.6 8.5": ["cowlings"], "6.2 -0.4 19.2": ["chau"], "11.7 6.8 17.6": ["grassier"], "-5.2 4.8 3.2": ["subarachnoid"], "1.1 11.9 3.6": ["wudu"], "2.7 13.4 10.7": ["tomove"], "12.7 -2.2 3.7": ["tabes"], "3.9 2.3 19.4": ["spongeworthy"], "-4.1 5.8 5.0": ["rheumatologic"], "12.6 22.5 10.6": ["keffiyah"], "9.7 17.8 46.2": ["goldeneyes"], "3.6 -2.6 8.4": ["redding"], "0.1 8.7 10.1": ["kallah"], "2.0 14.0 7.0": ["indemnitor"], "-2.1 2.7 2.6": ["peroneal"], "-0.0 18.4 -0.4": ["insistences"], "11.5 13.4 3.1": ["vooks"], "15.8 7.5 2.2": ["railworkers"], "-3.9 11.6 13.8": ["annuitizing"], "10.7 9.5 22.7": ["appletinis"], "4.9 8.7 2.1": ["wheeltracks"], "6.0 9.1 19.2": ["ruefulness"], "14.0 3.7 9.8": ["soulster"], "8.2 3.3 6.4": ["cyclothon"], "1.4 19.8 16.0": ["foreparents"], "5.9 7.6 18.0": ["unstrained"], "7.7 21.6 17.3": ["underhook"], "5.4 5.8 27.6": ["asafetida"], "8.9 0.4 5.1": ["dekatherm"], "0.2 0.6 18.8": ["matchman"], "17.1 2.2 5.9": ["quintuples"], "-4.8 14.0 10.9": ["mosts"], "14.6 15.3 20.4": ["gregariously"], "23.1 11.5 11.4": ["gridlike"], "24.9 7.4 7.5": ["postmerger"], "11.7 25.0 3.5": ["valorizing"], "5.2 9.0 6.9": ["neurturin"], "7.8 20.8 15.9": ["hendo"], "6.7 -1.2 10.8": ["iddo"], "13.6 25.3 10.3": ["proletariats"], "12.6 19.9 25.8": ["antiwhaling"], "4.4 2.7 4.7": ["voz"], "13.6 10.6 4.7": ["swtich"], "10.7 13.3 2.9": ["eroticised"], "21.4 10.2 16.6": ["curbstone"], "1.1 19.0 4.6": ["iand"], "16.5 9.8 11.6": ["sciencey"], "4.2 16.1 9.2": ["repentence"], "11.6 7.5 11.7": ["disapeared"], "8.9 1.6 7.5": ["worldsteel"], "8.5 7.9 28.7": ["kou"], "13.1 11.5 12.7": ["soundmen"], "23.0 10.2 26.1": ["poopie"], "-1.6 -1.1 2.9": ["ading"], "3.1 3.9 4.0": ["tfl"], "4.0 7.1 6.8": ["anodic"], "-1.5 8.5 1.3": ["identikits"], "13.0 20.7 12.9": ["hypervelocity"], "4.4 24.9 -2.1": ["outflanks"], "0.6 -0.8 4.4": ["mform"], "13.2 18.7 16.4": ["aquiline"], "22.8 4.1 26.5": ["ironbark"], "14.9 9.4 9.3": ["platens"], "10.2 15.9 11.8": ["dsi"], "12.1 11.1 20.1": ["wester"], "6.1 9.0 11.1": ["nigel"], "2.0 9.1 11.2": ["tagup"], "1.8 0.1 -5.9": ["accordng"], "14.6 -0.6 9.5": ["empresas"], "3.1 13.2 8.6": ["cyfluthrin"], "11.9 6.7 22.6": ["noonish"], "9.0 17.1 12.0": ["bobos"], "11.3 14.5 20.1": ["glover"], "8.8 15.5 3.7": ["forcer"], "7.4 15.5 13.9": ["awkard"], "-0.5 3.4 8.9": ["chemos"], "3.6 7.3 13.9": ["melam"], "3.8 14.4 13.7": ["thesevenveils"], "5.4 14.2 7.5": ["igbo"], "14.0 8.2 10.1": ["homewrecking"], "6.2 -1.3 11.0": ["tihs"], "-0.3 7.4 14.7": ["heim"], "10.1 7.4 21.2": ["bullnose"], "17.7 6.5 11.7": ["musem"], "1.7 -1.2 11.5": ["derm"], "11.0 15.5 14.6": ["bodhisattvas"], "5.3 10.5 6.8": ["absorbingly"], "6.1 4.8 -2.0": ["specifc"], "-1.8 -1.7 -4.2": ["mtm"], "5.0 17.8 -0.2": ["traducing"], "10.1 4.7 24.4": ["babi"], "5.6 20.5 3.0": ["unjustness"], "-3.2 13.5 -0.8": ["interveiw"], "6.1 9.2 17.3": ["kae"], "12.9 6.8 15.8": ["peepal"], "22.1 13.5 17.6": ["crissakes"], "14.2 20.9 12.1": ["cajolery"], "8.1 10.5 12.9": ["photosystem"], "3.2 4.2 3.2": ["fluorination"], "6.0 11.3 6.2": ["foreswore"], "0.3 2.3 3.8": ["neurosensory"], "8.3 -4.7 4.0": ["gurgaon"], "1.8 13.5 4.8": ["fansubs"], "7.8 7.6 9.9": ["bootblack"], "4.6 18.2 10.6": ["yishuv"], "0.3 -0.9 -2.4": ["commi"], "3.5 11.9 2.6": ["twoway"], "19.4 24.5 8.1": ["sallied"], "1.8 7.1 7.5": ["jakarta"], "14.8 8.0 17.5": ["moulins"], "10.9 -1.4 4.8": ["kyboshed"], "4.0 9.7 12.1": ["uniaxial"], "5.8 15.7 19.3": ["palila"], "4.7 -6.8 14.3": ["allottment"], "-1.0 12.3 4.3": ["underestimations"], "7.3 10.1 9.2": ["elemen"], "-5.5 5.9 13.1": ["alis"], "15.7 12.6 14.9": ["hoorays"], "2.9 12.4 15.9": ["habited"], "10.3 8.4 2.4": ["databased"], "18.6 19.9 10.5": ["globaloney"], "7.9 19.2 20.4": ["snowsqualls"], "16.1 5.8 16.9": ["deepwaters"], "9.3 9.8 20.2": ["hairstreak"], "3.8 7.1 16.4": ["baje"], "17.5 17.2 13.3": ["desolately"], "10.1 -0.8 9.0": ["muestra"], "8.7 12.7 14.8": ["vajazzle"], "-8.6 13.1 1.2": ["favortism"], "-4.2 -0.7 4.5": ["omiganan"], "10.7 13.9 12.6": ["nutritionism"], "4.6 7.0 26.7": ["superferry"], "-4.5 -5.1 4.8": ["reablement"], "6.5 7.7 11.9": ["misdelivered"], "3.5 4.1 12.1": ["chruch"], "12.0 2.0 13.6": ["milfs"], "29.8 8.2 8.3": ["brickmaker"], "-5.1 6.1 17.3": ["usapan"], "-6.4 8.6 9.7": ["rigourously"], "11.7 -3.8 11.6": ["nuovi"], "9.7 3.1 -0.3": ["techn"], "9.9 8.9 7.4": ["chromatherapy"], "21.7 4.7 8.6": ["msft"], "21.8 8.5 12.6": ["spinnerets"], "4.5 8.2 4.3": ["electrokinetic"], "3.0 18.2 7.9": ["naggy"], "8.0 11.1 -2.1": ["promotive"], "2.5 2.8 -3.7": ["arlier"], "7.5 26.5 19.5": ["halberd"], "-3.7 4.0 2.8": ["assurity"], "-1.0 14.7 8.7": ["moneybomb"], "-3.3 10.5 2.2": ["guity"], "9.4 16.3 17.6": ["conic"], "-7.6 13.7 10.5": ["lividity"], "21.2 3.7 24.9": ["schefflera"], "5.4 4.4 2.6": ["agribusinessman"], "9.2 18.7 14.9": ["avin"], "12.2 11.1 23.0": ["huggin"], "2.5 10.1 18.1": ["baya"], "13.0 10.9 5.8": ["wideboy"], "10.9 22.5 9.2": ["inuendo"], "3.6 10.7 2.1": ["konw"], "6.4 9.0 6.6": ["hopeing"], "9.1 12.8 26.0": ["usu"], "3.1 7.8 14.4": ["hati"], "-3.0 17.0 2.0": ["psycological"], "2.8 33.9 2.9": ["firebases"], "8.1 16.2 9.9": ["wget"], "10.2 5.4 7.6": ["contoversial"], "10.5 9.0 15.8": ["carboys"], "-5.8 12.9 11.0": ["congruently"], "12.3 26.4 3.2": ["effectivly"], "16.6 12.9 16.0": ["betulin"], "2.9 8.4 9.8": ["pilferages"], "1.8 -3.7 6.9": ["hydroxyzine"], "4.9 -4.7 2.0": ["agosto"], "24.1 20.7 30.7": ["crawlies"], "5.1 11.4 38.3": ["subtidal"], "13.3 14.9 28.9": ["speedwell"], "4.4 -1.6 5.3": ["unstarted"], "8.3 4.5 13.6": ["tinto"], "10.1 15.3 16.3": ["klap"], "-2.9 9.6 6.9": ["mesentery"], "16.3 7.8 21.9": ["shute"], "5.7 2.6 10.5": ["polydextrose"], "6.5 8.1 11.1": ["distributary"], "7.5 8.0 12.5": ["thumbhole"], "5.5 28.8 11.7": ["roleplayer"], "11.9 -1.2 -1.8": ["hotelicopter"], "0.1 2.3 -2.0": ["ibudilast"], "2.0 17.0 6.0": ["homosocial"], "9.1 -0.7 9.5": ["sizings", "demoliton"], "12.9 19.7 18.4": ["passtime"], "2.6 13.0 6.7": ["kinaesthetic"], "-1.7 10.1 4.8": ["gones"], "10.7 12.1 17.3": ["metallica"], "5.7 16.8 9.2": ["maynot"], "4.4 -4.1 -2.2": ["respondees"], "-0.3 7.2 12.1": ["superparamagnetic"], "16.5 17.4 22.1": ["cobber"], "7.1 27.0 4.4": ["unadaptable"], "6.2 6.7 13.6": ["herbaria"], "6.4 11.8 19.4": ["skelly"], "8.8 12.6 14.3": ["preheats"], "5.1 6.6 14.7": ["buveera"], "1.8 1.0 11.2": ["trevor"], "16.6 10.5 36.5": ["poisson"], "8.6 5.6 13.3": ["keyframing"], "10.4 14.3 13.8": ["surfboarding"], "-2.9 14.5 -1.4": ["underdetermined"], "8.0 9.7 26.3": ["snowcaps"], "17.0 24.0 16.1": ["dreamcast"], "3.2 6.4 9.2": ["afc"], "13.0 7.6 18.3": ["daley"], "3.4 1.5 13.0": ["bish"], "11.0 6.0 14.4": ["spellchecking"], "4.3 -2.8 20.5": ["nonvegetarian"], "-4.5 13.6 3.7": ["decompensate"], "4.7 -1.9 12.4": ["bst"], "4.0 9.8 15.5": ["bayram"], "-0.8 2.2 6.6": ["visita"], "2.8 3.7 14.5": ["midnite"], "4.4 1.5 10.2": ["redrilled"], "3.2 3.8 10.6": ["fejn"], "6.1 14.6 14.8": ["martensite"], "3.9 15.9 3.2": ["frien"], "-4.0 13.2 -3.8": ["elations"], "3.1 25.3 5.6": ["hetman"], "11.6 6.2 6.8": ["anag"], "5.5 4.6 2.3": ["telephonists"], "7.0 8.0 10.9": ["chromatogram"], "15.8 12.4 22.7": ["mummer"], "19.9 3.3 8.8": ["lamposts"], "9.0 6.1 0.7": ["circuited"], "12.6 15.9 20.4": ["rainin"], "2.5 5.1 10.7": ["nagiging"], "-2.1 12.8 4.0": ["theywill"], "0.7 2.9 12.4": ["unitemized"], "12.8 18.7 9.6": ["khakhi"], "7.4 6.2 13.5": ["quavery"], "13.4 29.6 9.4": ["blitzkriegs"], "7.4 3.9 9.4": ["amortisations", "probablly"], "-10.4 -4.4 -5.3": ["excusal"], "8.1 11.6 12.6": ["horseriders"], "1.0 15.6 8.7": ["poorness"], "7.7 16.7 7.8": ["transliterate"], "10.8 7.7 21.0": ["akita"], "-5.4 -2.2 9.7": ["noncollege"], "12.6 12.1 33.1": ["pikelets"], "-0.7 14.2 7.8": ["invariants"], "5.3 10.2 -4.2": ["genericized"], "6.8 2.4 15.5": ["owens"], "-2.0 13.2 2.6": ["cocalero"], "1.2 12.2 4.1": ["zambia"], "8.5 5.2 6.6": ["cottahs"], "29.9 5.3 9.1": ["eurostocks"], "4.2 13.1 13.7": ["zameen"], "14.4 11.9 7.1": ["yahooing"], "4.6 0.9 4.0": ["delicensing"], "-2.1 2.3 3.1": ["whlie"], "-2.3 15.2 6.1": ["amfortas"], "13.1 2.1 9.0": ["maching"], "4.9 6.0 19.5": ["lata"], "9.6 19.0 25.9": ["aedes"], "1.8 4.6 10.3": ["meke"], "8.1 7.1 13.9": ["dramtic"], "17.6 6.9 30.0": ["brioches"], "13.6 -10.8 -7.0": ["higlighted"], "1.2 6.1 1.6": ["afamelanotide"], "16.4 21.5 14.7": ["bathysphere"], "3.2 14.2 6.1": ["nichts"], "10.6 14.4 11.0": ["derny"], "6.1 16.1 16.4": ["bambini"], "12.3 4.1 0.7": ["andnot"], "0.6 -7.3 3.5": ["propyl"], "7.6 13.9 7.7": ["rubbermatch"], "8.0 9.4 5.2": ["pehaps"], "6.6 10.3 8.7": ["preprocess"], "27.4 -1.2 9.6": ["doubledecker"], "16.0 13.9 5.4": ["primadonnas"], "2.3 -4.7 9.2": ["struction"], "6.0 6.7 18.8": ["neeeded"], "-0.5 2.5 5.0": ["enterocolitis"], "-5.5 4.4 15.6": ["microdeletions"], "1.7 12.9 11.0": ["mulcting"], "8.4 9.1 14.0": ["camcorded"], "1.2 12.5 9.2": ["karke"], "1.7 26.1 13.0": ["ethiopia"], "4.3 33.9 10.0": ["unvanquished"], "7.7 -3.2 31.4": ["paya"], "10.5 5.3 9.9": ["columbite"], "7.7 15.6 -0.4": ["hestitation"], "3.9 18.7 3.1": ["inteference"], "10.8 17.5 33.8": ["pipit"], "5.4 6.6 20.9": ["breakfasters"], "4.0 3.1 12.2": ["connectorized"], "12.5 -0.7 -0.5": ["cadetships"], "8.4 16.7 3.3": ["outsing"], "19.9 6.5 5.8": ["enlargers"], "-1.7 9.0 17.8": ["veternarian"], "11.8 19.5 3.3": ["deathtoll"], "8.8 4.7 13.8": ["uplinkearth"], "10.1 11.8 9.3": ["pendejos"], "4.7 13.5 12.9": ["dampest"], "-5.9 11.1 4.1": ["constitutively"], "11.0 7.4 40.1": ["brininess"], "1.9 20.0 10.7": ["hotdogging"], "-6.4 6.8 11.6": ["saha"], "8.4 5.4 27.3": ["lber"], "-1.3 11.0 9.1": ["mushairas"], "17.6 -2.6 11.1": ["namebrand"], "16.0 27.1 11.3": ["ghastliest"], "16.5 4.8 7.1": ["alongisde"], "2.0 5.4 6.6": ["tamponade"], "-1.3 15.7 5.1": ["streng"], "17.0 1.5 27.5": ["konjac"], "1.4 15.9 7.4": ["dubiety"], "7.4 26.6 9.3": ["wavefunction"], "3.8 23.2 2.6": ["administraiton"], "4.2 6.6 12.6": ["serio"], "7.2 1.1 3.4": ["careworkers"], "9.7 0.2 13.7": ["vernon"], "1.0 14.9 -0.0": ["dakwah"], "10.8 10.6 11.5": ["tribeswomen"], "8.0 15.3 11.5": ["quels"], "6.5 8.7 14.6": ["plage"], "5.7 12.7 -1.7": ["racaille"], "4.7 0.5 -2.3": ["webside"], "5.9 26.3 -2.6": ["theire"], "4.4 -1.4 0.4": ["dbs"], "-1.6 -0.6 2.0": ["interclass"], "3.6 5.5 24.5": ["ladoo"], "12.9 7.9 31.9": ["titi"], "-4.3 6.8 10.0": ["indels"], "6.8 35.3 4.7": ["suicider"], "5.2 9.9 15.1": ["meningo"], "-8.3 4.1 1.9": ["lobar"], "5.1 23.5 11.9": ["sentimentalities"], "12.4 5.6 18.4": ["woodyard"], "0.2 8.5 2.2": ["hemoglobinopathies"], "16.7 8.1 23.2": ["dropcloths"], "8.4 3.9 3.8": ["modularised"], "12.7 12.6 18.2": ["inlaying"], "17.5 10.9 1.6": ["floodtide"], "3.2 7.2 7.9": ["guanosine"], "5.9 -9.0 5.4": ["threebedroom"], "-1.8 0.1 3.2": ["trospium"], "-3.2 12.4 5.4": ["annunciate"], "15.5 17.1 22.6": ["stomache"], "9.1 7.7 7.8": ["cubists"], "9.7 9.9 17.1": ["bolita"], "7.3 11.0 19.4": ["retighten"], "9.8 12.0 10.1": ["sierras"], "9.3 15.7 10.0": ["kibitzer"], "8.1 4.9 12.5": ["hyoid"], "4.3 5.9 8.8": ["reship"], "2.8 5.4 7.0": ["palabras"], "-4.5 6.5 -3.3": ["deputationists"], "6.4 10.8 11.9": ["multiperson"], "10.5 13.2 5.5": ["bruisingly"], "19.3 3.0 11.5": ["drome"], "8.1 13.7 9.0": ["vuln"], "13.0 -7.8 10.6": ["labratory"], "8.0 2.6 2.9": ["repored"], "6.6 12.1 8.5": ["aleph"], "16.0 15.5 24.3": ["cinerea"], "9.2 18.3 12.5": ["parleying"], "2.8 11.2 -0.6": ["epicist"], "26.7 24.9 20.7": ["bolas"], "7.2 10.3 8.3": ["ninguna"], "22.7 10.2 27.2": ["cowpat"], "12.8 18.9 6.8": ["interpenetrating"], "8.2 10.9 13.6": ["keed"], "16.3 13.1 24.8": ["rasberry"], "-0.8 4.3 9.1": ["bie"], "0.3 15.2 8.4": ["gangman"], "5.0 21.7 15.2": ["leishmania"], "10.5 21.0 12.6": ["recolor"], "17.7 10.6 7.5": ["scandalmongering"], "-7.4 -4.0 6.2": ["sition"], "-2.5 8.2 15.4": ["handa"], "-4.5 23.3 -4.3": ["disserves"], "5.6 6.8 9.3": ["auditionee"], "21.6 10.6 25.5": ["tannenbaum"], "-1.1 8.4 9.2": ["pulvinar"], "9.7 4.2 4.4": ["forcasting"], "6.3 14.4 3.5": ["similarily"], "7.7 -0.3 18.6": ["ngok"], "-2.5 9.8 13.6": ["mastoid"], "7.0 -0.4 4.4": ["paypacket"], "13.6 10.6 9.3": ["antireflective"], "6.5 20.3 4.7": ["laicite"], "12.6 18.3 19.6": ["boogy"], "2.2 -3.6 3.4": ["canadienne"], "1.6 6.2 10.1": ["unmarrieds"], "6.0 7.9 14.9": ["detrital"], "2.0 -4.8 3.7": ["lund"], "4.1 7.5 10.0": ["fishplates"], "17.9 5.7 32.7": ["spatzle"], "-3.8 1.9 14.5": ["laro"], "-2.8 1.6 8.8": ["adherance"], "22.2 13.1 17.7": ["protoplanets"], "0.4 16.8 18.9": ["tsetse"], "13.6 -1.6 -0.1": ["isheadquartered"], "0.1 11.1 6.7": ["trialers"], "12.2 13.0 11.7": ["eyecatcher"], "4.6 20.5 9.4": ["pitts"], "-7.3 6.8 5.7": ["theissue"], "1.0 17.3 10.4": ["nidus"], "-4.1 7.0 14.3": ["kokua"], "7.4 5.8 14.0": ["bauer"], "-1.6 -1.3 1.4": ["coursepacks"], "17.5 20.1 18.9": ["mame"], "-8.8 14.4 6.2": ["tothis"], "1.7 9.2 7.0": ["myopathies"], "16.4 11.2 12.3": ["meeter"], "1.8 8.4 3.5": ["rfb"], "17.8 18.2 13.2": ["burster"], "12.2 18.6 10.7": ["stumblebums"], "-9.4 0.9 -1.3": ["tutorage"], "8.9 15.4 8.3": ["mayhave"], "12.2 1.0 8.0": ["thermoelectricity"], "8.2 15.2 3.9": ["rumoring"], "9.3 19.8 2.5": ["peackeepers"], "3.7 4.4 0.0": ["controverial"], "9.7 15.6 10.9": ["shlubby"], "11.4 2.1 1.4": ["disolved"], "1.2 5.0 11.1": ["argentite"], "11.6 0.1 9.0": ["fairpark"], "5.2 11.1 21.4": ["introgression"], "11.1 11.9 30.0": ["sapote"], "5.6 6.0 7.0": ["ballkid"], "9.1 6.5 11.0": ["depanneur"], "14.7 0.0 17.1": ["mudflap"], "-9.6 2.3 11.8": ["anan"], "0.2 5.0 17.7": ["safed"], "6.0 11.0 6.9": ["leela"], "24.9 14.6 14.5": ["vuvu"], "13.3 14.0 25.0": ["mottle"], "23.1 15.5 25.7": ["blowguns"], "17.8 11.1 12.3": ["jobbies"], "4.9 8.9 5.8": ["pricers"], "12.5 12.1 17.1": ["tarseal"], "4.7 0.7 6.1": ["ril"], "8.2 5.5 29.7": ["boucherie"], "0.7 3.7 8.4": ["nabilone"], "17.0 8.9 44.6": ["mudsuckers"], "11.7 11.9 6.8": ["weakeness"], "-8.1 12.2 8.0": ["givng"], "-1.2 12.9 7.1": ["colocalization"], "-4.3 3.8 0.1": ["eyeon"], "5.7 0.6 10.8": ["spacier"], "7.9 8.5 9.3": ["donw"], "6.1 13.6 10.4": ["hourlies"], "8.5 0.2 -0.1": ["trailled"], "27.7 26.5 8.4": ["superintelligent"], "6.1 6.2 2.9": ["milliards"], "6.2 -2.5 10.5": ["microemulsion"], "-2.8 7.7 -5.0": ["reprehensive"], "2.4 9.8 -9.6": ["camapaign"], "3.2 6.8 11.4": ["deduping"], "7.6 3.0 9.6": ["digitisers"], "2.4 4.4 4.0": ["intimal"], "24.6 16.3 15.5": ["polyhedron"], "5.2 4.7 6.1": ["wonderstruck"], "7.9 4.2 0.8": ["mbed"], "4.1 7.1 20.7": ["bronx"], "3.3 6.7 8.2": ["commonstock"], "4.2 3.7 0.8": ["gover"], "13.0 4.3 24.9": ["armorial"], "17.1 -1.3 10.4": ["rebilling"], "9.7 7.3 21.4": ["menehune"], "3.9 29.1 -1.9": ["instrumentalization"], "18.4 19.4 17.1": ["fraulein"], "13.4 4.1 15.6": ["brack"], "3.8 1.9 8.7": ["vjt"], "3.7 7.0 15.6": ["feedline"], "5.5 11.8 12.8": ["telemarket"], "1.9 11.1 14.1": ["robben"], "-0.1 -1.5 -0.9": ["spokesperon"], "1.5 6.6 -0.2": ["quashment"], "7.0 0.6 8.9": ["drupal"], "7.1 14.1 10.9": ["saran"], "8.0 4.7 13.4": ["alkalic"], "6.3 11.6 24.5": ["fleabane"], "1.8 12.3 2.2": ["monogamist"], "14.3 19.9 10.6": ["discordantly"], "1.4 12.8 7.1": ["todayand"], "1.2 4.2 5.1": ["webchannel"], "11.2 9.8 6.8": ["pyramided"], "5.6 10.4 9.6": ["djellaba"], "12.2 7.4 9.8": ["sketchers"], "12.1 11.4 16.6": ["kachinas"], "3.7 4.5 20.2": ["welland"], "9.7 8.1 10.5": ["thrus"], "-1.8 13.3 3.0": ["actio"], "1.4 3.1 3.3": ["mudaraba"], "5.8 12.9 22.2": ["garigue"], "7.3 11.1 11.4": ["canalization"], "4.0 -5.8 4.7": ["commisison"], "15.0 9.8 3.0": ["autoinsidernews"], "0.5 3.9 5.4": ["propshafts"], "11.8 4.0 11.2": ["thermochromic"], "-4.9 1.4 8.1": ["troglitazone"], "2.5 7.9 14.4": ["srv"], "14.0 5.9 7.5": ["seguridad"], "14.1 12.8 12.5": ["laissez"], "11.4 7.1 7.4": ["downlighters"], "6.4 13.1 12.1": ["damascene"], "-7.6 14.7 1.0": ["coachee"], "18.7 15.7 2.5": ["aother"], "-1.5 15.0 12.4": ["maydays"], "-0.8 15.3 9.6": ["pyschologically"], "5.7 18.8 10.7": ["gonner"], "3.3 3.3 2.3": ["geodatabases"], "-0.3 5.6 -0.9": ["simplier"], "1.4 11.4 1.9": ["dyadic"], "-4.3 2.9 4.9": ["epoprostenol"], "19.0 6.4 12.9": ["allsorts"], "14.2 7.7 23.1": ["snowcap"], "7.4 7.9 7.8": ["thae"], "-0.7 4.5 10.7": ["lona"], "-0.7 6.0 5.9": ["papilledema"], "6.1 17.0 9.3": ["mentals"], "19.7 4.7 10.9": ["funkily"], "12.3 -1.3 5.0": ["jul"], "16.0 8.4 27.0": ["bentos"], "-0.9 -0.6 5.5": ["speedcar"], "8.8 1.5 30.1": ["panamaxes"], "0.1 15.9 10.4": ["impass"], "8.4 -0.7 6.8": ["oltre"], "15.3 5.0 16.8": ["austral"], "6.2 6.2 6.7": ["churchlike"], "9.2 16.7 26.3": ["cotyledons"], "7.4 1.9 28.9": ["jambon"], "5.4 10.0 24.0": ["laths"], "12.3 2.1 2.9": ["heterostructure"], "0.9 -1.8 14.1": ["flores"], "3.8 2.8 1.0": ["percet"], "9.4 16.9 16.7": ["megastate"], "-2.8 12.5 4.7": ["uncurable"], "10.6 7.3 16.7": ["butterly"], "14.4 6.0 18.8": ["inviable"], "10.4 3.2 7.2": ["minorleague"], "5.5 10.9 3.3": ["antiseizure"], "-1.0 24.1 0.8": ["grevious"], "4.7 10.9 10.6": ["goint"], "1.7 -1.7 6.0": ["ladderized"], "5.5 4.2 8.5": ["tunica"], "2.9 7.5 13.3": ["rickshawpullers"], "-8.3 26.0 6.4": ["kandaks"], "-5.5 8.0 -1.9": ["rizatriptan"], "7.7 4.5 11.6": ["anear"], "9.8 1.9 13.0": ["stretchier"], "5.1 -0.4 14.3": ["kinders"], "11.5 9.3 11.5": ["unhitching"], "6.1 1.3 5.5": ["unlet"], "4.4 -8.4 4.8": ["ior"], "10.0 2.2 6.0": ["ethicality"], "6.8 8.4 -1.1": ["allegdly"], "0.8 9.2 12.4": ["thelocal"], "14.0 5.3 29.2": ["kowhai"], "8.2 7.9 14.3": ["environmentals"], "12.3 12.3 21.1": ["nargile"], "9.3 3.6 6.1": ["lyocell"], "22.3 16.0 45.9": ["cods"], "9.5 18.4 16.5": ["forsooth"], "-2.0 3.5 12.1": ["hepatoblastoma"], "12.1 3.7 13.1": ["postgresql"], "5.3 6.5 11.5": ["shakespeare"], "3.6 1.2 16.7": ["onda"], "16.2 0.6 27.3": ["fromagerie"], "-9.1 8.0 6.5": ["elctions"], "3.8 12.2 10.3": ["drfillgood"], "-2.4 9.1 15.5": ["multicabs"], "-1.6 10.8 4.3": ["reductil"], "-3.0 11.6 14.9": ["ultrarunners"], "10.5 12.5 9.1": ["inbalance"], "6.3 5.7 5.5": ["oneman"], "11.0 8.6 5.6": ["songless"], "12.1 7.7 -5.5": ["programmeme"], "-1.9 28.6 10.0": ["bitterer"], "-0.5 10.2 6.5": ["correlators"], "-0.8 6.1 0.4": ["intrinsics"], "-0.4 6.2 14.7": ["silviculturist"], "9.8 15.5 6.2": ["hatemail"], "12.7 16.2 10.3": ["aliased"], "12.5 17.4 15.1": ["comprimise"], "5.0 27.1 12.8": ["skillshots"], "18.1 5.9 15.6": ["retarders"], "9.7 5.5 4.2": ["logitech"], "0.1 2.5 3.2": ["gls"], "12.6 9.9 53.6": ["wolffish"], "-0.1 19.4 3.1": ["loktantra"], "7.2 12.6 10.5": ["pappa"], "-2.6 14.4 14.1": ["briefness"], "3.7 9.6 17.7": ["sisi"], "8.6 3.8 15.4": ["veneering"], "10.3 38.9 10.0": ["counterstrategy"], "-7.6 -2.5 -2.4": ["nonobservance"], "3.2 -8.6 7.6": ["giugno"], "6.6 9.9 13.4": ["litttle"], "8.6 3.1 16.5": ["tutto"], "8.1 3.0 3.0": ["accroding"], "-0.8 -0.7 6.1": ["relinquishments"], "12.7 15.1 6.4": ["novas"], "16.5 2.4 14.1": ["agarbatti"], "4.7 17.7 3.7": ["unconsious"], "4.1 10.3 13.4": ["campily"], "16.2 12.7 44.8": ["ulua"], "0.1 15.2 13.9": ["looke"], "0.6 6.1 15.9": ["nanquan"], "-12.5 4.2 2.9": ["taff"], "10.1 15.8 6.7": ["photolyase"], "4.3 9.1 10.8": ["prendre"], "8.3 -1.0 2.4": ["andtechnology"], "4.3 23.7 8.5": ["proslavery"], "3.9 31.3 6.6": ["indignations"], "-0.1 4.5 11.0": ["metaphyseal"], "3.4 14.8 0.5": ["strenghthen"], "-1.3 14.0 2.4": ["ohmic"], "-2.1 -1.0 2.8": ["cance"], "4.4 19.7 10.9": ["absoultely"], "4.9 4.6 3.3": ["potenial"], "10.4 -4.0 19.5": ["backcombing"], "14.1 8.5 24.8": ["vicunas"], "2.9 18.0 7.3": ["deboarding"], "15.4 5.0 9.5": ["municpal"], "12.4 9.1 14.4": ["bieber"], "9.7 15.2 8.5": ["soaringly"], "4.9 7.7 3.2": ["opporunities"], "4.4 16.0 2.8": ["delict"], "4.0 4.8 5.2": ["commemmorate"], "14.6 8.5 23.3": ["cossies"], "-7.2 -4.1 -5.3": ["enior"], "13.0 11.7 46.3": ["ciscoes"], "14.1 8.9 16.7": ["yowza"], "3.0 6.8 -2.4": ["potencial"], "9.3 5.9 8.5": ["abandonware"], "-0.1 5.9 15.9": ["striae"], "-1.6 3.6 1.9": ["minue"], "9.9 8.0 24.5": ["fucoxanthin"], "15.9 4.1 20.7": ["drabber"], "-1.9 17.6 10.3": ["shechitah"], "14.8 5.5 3.5": ["expertize"], "7.6 8.4 2.1": ["pyrometer"], "10.4 2.6 -0.7": ["payware"], "17.6 17.6 14.4": ["underoos"], "25.9 7.0 29.7": ["bartop"], "0.9 3.8 7.1": ["jude"], "11.5 16.6 11.1": ["bigamists"], "2.8 4.7 1.5": ["enforcable"], "8.8 25.9 -3.6": ["defamer"], "-3.1 8.2 4.3": ["hydrops"], "-6.2 8.6 -4.9": ["questionning"], "5.7 4.8 12.4": ["augusta"], "-4.5 9.5 13.6": ["isotherm"], "10.0 3.8 11.5": ["conomic"], "7.7 19.2 6.3": ["thepolice"], "13.0 16.5 11.4": ["cacophany"], "6.5 9.8 5.6": ["syndrom"], "11.7 2.6 22.4": ["grisaille"], "7.0 1.6 11.7": ["starr"], "1.3 7.5 8.1": ["caus"], "11.2 20.7 18.1": ["wafflers"], "10.5 1.9 18.7": ["malibu"], "17.2 3.8 26.8": ["honeyeaters"], "19.4 11.6 11.3": ["slimly"], "-3.2 1.3 10.8": ["clea"], "-1.0 6.8 8.4": ["outgamed"], "1.6 5.3 13.7": ["gawkiness"], "10.8 0.2 8.7": ["monickers"], "1.2 -0.4 1.5": ["twoweeks"], "7.5 7.2 6.2": ["kilomters"], "-4.4 13.1 8.9": ["bentleywire"], "10.4 2.2 -1.0": ["surounding"], "7.2 2.1 7.9": ["productised"], "9.0 -4.4 6.0": ["tecnologia"], "2.2 6.0 8.7": ["reinvited"], "-1.4 20.5 9.5": ["adaptogen"], "6.1 16.3 12.1": ["lowballs"], "7.0 1.9 9.0": ["catechetics"], "1.9 -5.0 4.2": ["onlineprnews"], "-3.5 5.3 2.1": ["sympathectomy"], "8.3 9.9 26.2": ["lamium"], "0.2 22.1 4.2": ["decolonized", "cytolytic"], "10.1 23.6 10.4": ["seeketh"], "1.8 -0.8 -5.5": ["privat"], "-5.6 7.0 8.0": ["undischarged"], "19.5 10.0 17.0": ["palais"], "7.2 5.6 8.1": ["subdistributor"], "15.4 4.1 1.0": ["nastygram"], "-4.3 -6.0 2.1": ["tuhn"], "7.4 -0.0 10.3": ["cannulated"], "2.3 15.5 12.1": ["copilots"], "5.4 7.3 23.8": ["overskirt"], "-9.4 -5.7 5.5": ["repsectively"], "-1.0 12.8 10.9": ["topeka"], "-0.1 20.1 3.8": ["sanjay"], "-1.8 21.3 8.7": ["policework"], "2.9 7.7 15.5": ["angustifolia"], "5.4 16.0 35.3": ["grosbeak"], "12.6 9.3 9.7": ["istas"], "-3.4 4.3 7.0": ["urothelial"], "2.6 3.9 0.6": ["radiotracers"], "3.8 7.0 9.2": ["gomez"], "13.7 17.5 17.7": ["yammers"], "2.6 7.1 7.6": ["afair"], "17.4 -1.5 10.7": ["reclad"], "10.4 5.3 10.3": ["mapquest"], "-3.8 8.2 -6.5": ["querried"], "3.1 -0.5 11.2": ["unrhyw"], "16.3 5.6 29.6": ["fishmarket"], "3.0 14.7 11.0": ["seamhead"], "2.0 0.4 9.0": ["artis"], "5.0 1.7 5.8": ["ferrites"], "10.8 -1.1 3.8": ["noninvestment"], "3.8 20.4 10.8": ["adhocism"], "15.4 4.8 14.3": ["geordie"], "3.9 10.6 4.5": ["concieve"], "4.3 9.6 3.2": ["borohydride"], "3.2 7.2 14.0": ["solopreneurs"], "4.2 5.0 17.8": ["gallimaufry"], "3.4 -2.4 4.2": ["postapproval"], "12.4 -0.5 -0.3": ["withits"], "11.1 0.6 0.3": ["itsr"], "8.3 -1.9 6.1": ["mostof"], "5.6 11.8 8.8": ["hetrosexual"], "8.9 20.9 14.7": ["grindy"], "5.5 17.9 3.3": ["coruption"], "11.2 2.2 3.1": ["manometers"], "8.8 8.9 4.7": ["goalgetter"], "22.0 14.3 30.4": ["snoots"], "11.9 6.8 4.4": ["boad"], "2.3 1.5 6.8": ["clin"], "8.5 19.8 24.4": ["omoplata"], "9.9 11.3 11.0": ["newie"], "4.3 4.8 14.6": ["taffetas"], "-0.5 7.8 9.3": ["bastis"], "9.0 9.5 10.8": ["descramble"], "-3.2 15.1 -0.7": ["overtest"], "-0.8 10.4 13.3": ["laterites"], "13.3 5.0 18.7": ["predinner"], "1.6 5.0 15.6": ["recrystallization"], "0.8 7.6 9.7": ["isoleucine"], "3.4 -2.4 7.7": ["musicales"], "2.6 0.3 10.2": ["supersectors"], "6.2 7.4 13.3": ["androstadienone"], "10.3 9.1 21.4": ["chandan"], "17.7 12.1 19.8": ["claylike"], "4.1 8.7 16.1": ["sulfidation"], "0.0 1.1 8.0": ["pjg"], "0.4 18.0 3.8": ["fictionalise"], "-1.1 11.8 6.5": ["mouza"], "19.0 6.6 20.7": ["cree"], "4.8 4.9 12.9": ["metalcutting"], "6.2 24.4 5.5": ["legionary"], "9.5 12.8 32.7": ["windjammers"], "10.1 15.4 15.4": ["chlorophyl"], "17.1 22.5 24.6": ["daggum"], "2.4 1.9 15.4": ["expeced"], "1.6 5.3 9.6": ["welcom"], "1.9 0.5 5.7": ["nonreporting"], "7.3 -3.4 7.4": ["semana"], "16.0 12.0 16.1": ["pinwheeled"], "3.7 5.2 5.7": ["linecutting"], "11.3 1.9 18.7": ["bellringing"], "3.1 7.5 9.2": ["cise"], "5.8 12.3 18.7": ["coulters"], "-0.9 7.3 9.1": ["prehab"], "4.2 20.2 9.7": ["genealogically"], "1.9 16.8 7.4": ["sneek"], "13.7 -3.3 14.5": ["roche"], "13.1 6.2 35.6": ["spongecake"], "3.6 5.1 10.1": ["underproduced"], "4.3 18.4 5.2": ["grudged"], "2.4 6.4 11.1": ["capacitation"], "15.0 18.7 19.5": ["ridonkulous"], "-2.6 13.5 -8.4": ["khateeb"], "0.4 11.7 10.3": ["paralogs"], "6.1 7.0 14.5": ["limonitic"], "9.7 1.6 14.1": ["etchers"], "3.7 8.4 3.1": ["destigmatise"], "2.4 13.0 6.1": ["deprave"], "11.2 6.4 15.5": ["patens"], "9.6 1.6 7.5": ["osi"], "14.8 7.9 27.9": ["rayed"], "4.2 -8.3 -3.0": ["arl"], "10.5 -0.5 12.4": ["studes"], "10.3 7.7 18.1": ["icer"], "10.3 3.8 3.5": ["businesse"], "18.8 26.3 3.1": ["balkanised"], "10.6 8.6 20.1": ["fales"], "-7.2 1.2 7.1": ["skimeister"], "0.9 12.2 15.1": ["maby"], "10.8 4.3 9.8": ["haberdashers"], "12.0 9.6 9.4": ["horrorshow"], "-2.9 10.0 9.1": ["sabse"], "-2.7 -0.7 9.7": ["tais"], "4.8 19.2 10.2": ["immunobiotics"], "-0.6 5.4 3.7": ["polymetalic"], "-1.3 7.1 13.8": ["townmates"], "-4.7 10.6 1.7": ["raf"], "4.6 -4.1 15.4": ["espagnole"], "14.7 19.5 29.6": ["ooohh"], "13.6 3.8 26.5": ["siamang"], "20.6 -4.5 3.1": ["billionn"], "-0.1 12.1 3.7": ["thyrotoxicosis"], "1.8 5.1 5.7": ["muncipality"], "14.0 18.0 22.7": ["cravate"], "5.6 19.4 2.8": ["footsy"], "8.0 0.6 9.1": ["mta"], "10.0 9.8 16.5": ["metasediment"], "-2.0 -3.0 5.3": ["consortial"], "12.0 18.8 10.0": ["onw"], "12.7 1.3 14.9": ["shadowboxed"], "7.5 -2.0 15.5": ["kj"], "16.1 8.8 0.5": ["disect"], "4.0 2.1 32.6": ["entrecote"], "-3.0 5.2 5.7": ["veritate"], "5.9 16.3 6.9": ["inspiriting"], "1.2 17.7 8.9": ["actinic"], "12.4 15.5 7.7": ["unbusinesslike"], "5.1 5.0 8.8": ["reconceptualization"], "2.4 2.5 16.9": ["essex"], "3.3 18.9 0.8": ["administartion"], "11.2 16.4 4.9": ["geosocial"], "15.1 2.9 3.0": ["fourpiece"], "5.6 17.7 15.3": ["didst"], "9.9 21.6 14.5": ["habbits"], "9.1 6.1 17.4": ["overheight"], "11.9 -1.0 13.2": ["brushings"], "12.3 6.7 28.4": ["stracciatella"], "3.7 12.3 -11.0": ["demonstation"], "-8.9 3.1 4.3": ["nicardipine"], "1.5 5.5 -4.6": ["thetransaction"], "15.2 6.1 14.4": ["unreeling"], "13.7 19.9 27.2": ["briers"], "-2.0 -0.4 14.5": ["regina"], "4.0 11.0 15.3": ["skintones"], "-3.6 3.4 4.3": ["centile"], "4.5 7.3 6.3": ["sermonettes"], "7.2 1.4 8.0": ["inboards"], "10.0 5.4 5.2": ["immortalises"], "5.6 8.9 7.4": ["decarbonizing"], "8.8 3.3 3.9": ["pannists"], "10.0 4.1 -1.8": ["helpd"], "9.3 12.6 25.4": ["gomphrena"], "10.7 8.4 11.3": ["handback"], "13.3 20.7 20.2": ["photosynthesise"], "5.8 6.1 9.7": ["csi"], "4.1 -1.6 5.9": ["semisynthetic"], "0.8 4.9 -1.6": ["objectional"], "14.1 0.6 4.2": ["courant"], "4.7 30.6 8.5": ["unperceived"], "5.4 4.8 4.2": ["careerlong"], "17.0 17.5 13.4": ["monocrop"], "16.8 8.6 15.2": ["uplight"], "1.6 2.8 4.7": ["becauase"], "7.6 18.7 19.0": ["bossier"], "-6.4 12.8 7.0": ["nachas"], "14.3 19.1 6.5": ["literaly"], "7.6 9.4 8.9": ["rudiment"], "16.3 8.2 -0.2": ["friendy"], "6.6 4.4 11.0": ["joyce"], "8.4 19.3 9.2": ["injust"], "20.0 5.4 22.3": ["saltworks"], "-4.1 0.6 15.7": ["nonrenewed"], "21.4 9.8 23.1": ["swanlike"], "11.1 20.3 8.3": ["rapers"], "18.7 20.2 36.1": ["peppergrass"], "-0.7 -1.7 1.8": ["impove"], "10.4 1.8 11.4": ["confect"], "9.4 13.6 12.4": ["fubar"], "8.5 14.1 5.7": ["incestual"], "8.4 4.9 16.0": ["pils"], "-2.5 3.8 20.2": ["yacon"], "8.6 -0.3 8.5": ["settting"], "14.2 3.7 5.6": ["girlz"], "8.8 23.7 6.4": ["eveybody"], "2.7 2.4 23.8": ["greco"], "3.6 0.6 13.2": ["crashfest"], "6.7 18.9 7.7": ["riflescope"], "12.6 5.2 13.7": ["jhatka"], "0.2 6.3 6.5": ["plainspeak"], "2.9 11.8 3.8": ["tribological"], "9.0 -0.6 13.2": ["tigher"], "-2.8 12.2 -1.8": ["polygraphy"], "9.4 8.3 10.4": ["interlisted"], "6.7 21.0 9.2": ["microstates"], "1.4 23.1 0.7": ["catastrophizing"], "6.8 1.6 -0.2": ["feratel"], "11.4 8.1 14.5": ["liftman"], "19.4 16.8 16.8": ["garryowen"], "18.8 9.4 30.3": ["chiton"], "14.1 12.8 27.6": ["pysanka"], "16.8 12.5 13.6": ["phallocentric"], "4.2 7.4 8.6": ["cuprate"], "-2.5 -1.3 3.1": ["ects"], "4.6 9.8 7.6": ["remonstrances"], "14.9 8.6 12.4": ["machinary"], "5.2 7.6 6.5": ["ungritted"], "9.4 38.5 9.9": ["tyrannizing"], "4.8 12.4 -0.5": ["sems"], "7.6 21.7 7.6": ["cacique"], "0.6 6.7 2.5": ["petiton"], "12.2 10.5 7.6": ["quadplay"], "5.4 5.9 3.8": ["progressa"], "11.8 10.7 9.5": ["gibed"], "-2.2 3.4 7.2": ["afebrile"], "5.7 10.5 12.8": ["prashanth"], "-3.3 12.4 3.0": ["sequela"], "6.1 3.1 9.3": ["shagun"], "5.1 5.2 5.0": ["quaility"], "20.1 7.7 13.2": ["mojos"], "-3.3 8.2 11.3": ["geogs"], "3.8 16.6 6.6": ["simi"], "15.2 23.8 5.4": ["gloatingly"], "13.6 22.9 13.0": ["infinitude"], "8.5 9.8 32.3": ["gooeyness"], "13.6 11.6 16.4": ["ffor"], "3.3 9.1 9.1": ["tsotsi"], "11.6 2.5 3.9": ["megwatt"], "7.2 8.0 3.9": ["campaig"], "-0.4 4.9 12.4": ["triazine"], "9.0 42.9 8.9": ["solidiers"], "2.3 12.8 8.7": ["ballscrews"], "15.1 20.2 14.4": ["burgler"], "22.5 5.2 24.1": ["ginko"], "-2.6 -4.2 -2.1": ["elete"], "1.7 11.1 4.8": ["chicklit"], "5.2 -0.4 1.0": ["credativ"], "-0.8 6.1 11.7": ["thks"], "28.5 9.7 17.6": ["botherer"], "16.5 21.1 11.6": ["witlessness"], "6.1 4.6 12.5": ["clitorises"], "8.0 6.0 22.1": ["rebreathers"], "25.0 19.2 16.5": ["hydras"], "0.1 2.3 3.9": ["nonscoring"], "-1.8 -0.5 11.5": ["reride"], "-3.1 13.4 2.7": ["unbeneficial"], "7.6 2.3 9.7": ["sawa"], "10.7 -3.1 10.5": ["repricings"], "8.7 8.3 5.6": ["daylit"], "13.0 15.7 11.0": ["ossifying"], "-4.1 2.0 -0.6": ["absents"], "-9.2 1.4 1.5": ["coodinator"], "8.2 5.6 6.3": ["runnability"], "17.1 10.8 1.6": ["nobbling"], "17.3 14.5 11.6": ["rumple"], "8.5 14.5 19.3": ["brodifacoum"], "-0.6 20.7 9.1": ["figh"], "13.0 22.0 9.7": ["spinelessly"], "7.3 14.4 8.6": ["unplumbed"], "2.4 -2.8 6.0": ["mda"], "1.7 6.2 8.0": ["adition"], "4.8 0.2 18.6": ["antihunger"], "4.9 9.5 13.0": ["hablar"], "9.2 17.6 7.6": ["ambigious"], "1.2 11.3 1.2": ["subcarriers"], "13.0 3.1 23.9": ["lindy"], "8.8 16.4 30.1": ["bowerbirds"], "11.8 9.3 32.3": ["passata"], "8.2 7.8 6.6": ["backout"], "6.1 7.0 9.0": ["julio"], "12.8 4.5 33.2": ["buffett"], "4.7 -0.3 -0.7": ["titanate"], "12.3 9.2 41.0": ["trouts"], "0.1 28.2 8.2": ["shaykh"], "16.3 22.0 24.1": ["thrillseeker"], "6.7 -1.6 3.1": ["rennovations"], "-6.8 -3.0 6.8": ["externs"], "2.4 9.8 18.6": ["sauvignons"], "5.5 19.8 21.9": ["abscission"], "11.5 1.7 6.0": ["worksharing"], "8.6 7.9 8.9": ["oversimplistic"], "7.6 19.7 23.6": ["boonie"], "17.7 0.7 11.4": ["serigraphy"], "-3.0 3.4 18.8": ["alicia"], "1.5 8.9 21.9": ["xau"], "12.4 8.9 5.3": ["cyanogen"], "-6.6 5.4 -5.2": ["gazzetted"], "2.6 13.4 8.0": ["args"], "3.8 24.7 10.2": ["nerfs"], "5.5 12.1 1.7": ["surley"], "12.1 15.7 6.0": ["beore"], "12.0 24.8 3.7": ["happends"], "1.9 5.3 7.9": ["bitchier"], "29.7 6.2 2.9": ["paintmaker"], "13.8 6.2 16.7": ["lyres"], "11.9 5.7 12.8": ["microfleece"], "-4.5 4.5 3.3": ["starte"], "-0.7 12.2 9.7": ["dein"], "10.6 9.7 2.0": ["bussss"], "9.0 8.3 12.4": ["revers"], "-1.6 10.2 3.1": ["potentiating"], "10.2 20.3 12.3": ["librul"], "3.2 17.0 11.1": ["overrates", "ajeeb"], "-5.4 4.5 0.4": ["tonometry"], "18.5 1.5 15.3": ["minimall"], "2.7 10.3 23.4": ["oakiness"], "-2.9 9.3 22.4": ["moistures"], "10.3 -0.3 4.8": ["overdelivering"], "18.6 18.3 13.5": ["belays"], "18.9 36.3 6.4": ["superweapons"], "7.6 8.9 10.7": ["volta"], "-1.2 19.2 6.3": ["circumscription"], "6.2 11.6 20.6": ["offtrack"], "10.3 13.0 8.1": ["yop"], "18.2 27.5 14.2": ["sicking"], "15.3 11.8 28.7": ["girthy"], "-2.2 15.6 -0.4": ["reconnoitred"], "1.0 -3.8 3.3": ["inca"], "2.6 17.4 7.6": ["unnecesary"], "6.2 3.4 37.8": ["crostinis"], "1.6 10.1 5.8": ["velafermin"], "-3.5 17.8 3.1": ["dispensationalist"], "5.5 10.9 11.8": ["specularite"], "1.4 7.5 3.1": ["indigeneship"], "11.8 21.6 1.9": ["ubermensch"], "17.6 14.0 19.1": ["furler"], "8.3 5.6 10.4": ["agroindustrial"], "2.8 -7.9 4.4": ["viewbook"], "9.1 14.0 4.4": ["bigmen"], "5.0 33.8 8.0": ["multilateralists"], "8.5 10.2 18.8": ["sattu"], "3.8 20.9 11.3": ["unfalteringly"], "0.9 -0.7 13.6": ["kuei"], "-5.6 16.4 -2.1": ["deviationist"], "1.5 1.2 5.2": ["greement"], "-3.5 13.8 9.0": ["reoffenders"], "7.1 15.6 14.8": ["willis"], "-1.2 4.3 10.2": ["ulous"], "5.2 10.8 15.0": ["freeganism"], "-8.4 10.8 5.9": ["releived"], "5.0 12.0 45.1": ["tahong"], "6.7 6.8 10.6": ["cabbing"], "9.8 12.8 28.8": ["chickie"], "10.8 10.9 11.3": ["scintillatingly"], "1.8 4.6 -0.8": ["bullocked"], "-5.5 3.8 9.4": ["orridge"], "4.2 9.4 19.2": ["cementum"], "16.6 7.2 10.4": ["psalter"], "9.0 -0.1 9.9": ["bic"], "11.6 24.4 6.1": ["soverignty"], "-5.5 17.3 0.2": ["reliabilty"], "-0.7 -0.7 17.1": ["watermedia"], "25.2 10.4 11.6": ["superprofits"], "19.4 1.2 11.0": ["lexan"], "15.1 1.6 1.9": ["nigth"], "2.1 -1.5 0.9": ["hotfrog"], "11.3 12.2 7.6": ["timorously"], "22.5 11.8 18.2": ["jurassic"], "11.7 6.8 6.9": ["sortof"], "8.6 2.6 14.3": ["technopreneur"], "9.1 24.6 -3.3": ["counterspy"], "15.2 13.3 21.2": ["odalisque"], "10.3 14.4 15.4": ["bindu"], "1.9 8.5 1.8": ["transperancy"], "-3.8 -1.8 3.0": ["headboy"], "-2.3 6.3 8.8": ["saferanger"], "17.6 13.1 25.1": ["trichomes"], "-3.4 -3.3 -2.3": ["infoline"], "9.0 12.8 -0.1": ["nizam"], "-4.6 4.2 9.9": ["countersignature"], "5.9 -2.6 10.9": ["mik"], "14.3 14.3 6.3": ["ticktock"], "22.2 16.4 21.1": ["dinosaurian"], "14.2 12.9 16.6": ["bodyslams"], "19.7 6.5 17.4": ["snowscapes"], "-0.1 -0.9 8.1": ["circut"], "5.8 19.5 5.5": ["superciliously"], "3.0 3.7 10.7": ["bardoxolone"], "13.1 14.0 12.2": ["ohhhhh"], "1.3 27.9 8.0": ["citizenries"], "8.8 21.6 18.2": ["jove"], "28.7 11.4 23.0": ["snaggletooth"], "8.6 12.5 2.2": ["outwide"], "0.2 2.0 -3.2": ["ancotel"], "0.1 4.5 8.4": ["touchown"], "12.3 17.3 15.6": ["adulteresses"], "0.3 3.3 16.1": ["kulang"], "7.2 9.2 -0.6": ["profilic"], "9.8 22.8 -4.7": ["condign"], "4.6 6.0 6.5": ["lactone"], "6.3 16.3 2.2": ["ehem"], "-1.7 8.5 9.2": ["immunochemical"], "11.1 -10.2 11.4": ["requring"], "-3.3 9.6 7.0": ["bellcow"], "11.3 17.1 13.6": ["palpitate"], "10.2 20.6 -3.6": ["maneuvre"], "5.8 4.3 19.4": ["ergothioneine"], "3.5 5.4 13.0": ["socal"], "-1.0 1.9 5.2": ["immunoreactive"], "10.4 23.1 -0.9": ["disambiguate"], "-1.9 9.6 11.3": ["practicioner"], "3.7 7.6 9.7": ["oddmakers"], "13.6 -3.0 7.1": ["maart"], "21.3 10.8 39.4": ["suckerfish"], "7.6 20.1 7.9": ["bolds"], "3.8 11.2 8.4": ["unextinguished"], "-0.6 8.8 4.4": ["shabad"], "-3.2 1.8 6.4": ["prohormone"], "9.3 9.3 24.5": ["mukha"], "3.4 5.7 2.5": ["incre"], "0.9 2.0 9.8": ["reprovision"], "2.6 12.8 7.2": ["propety"], "3.6 4.6 14.9": ["edentulous"], "1.2 8.4 2.1": ["fibrocytes"], "7.3 0.8 -4.2": ["polarimeter"], "8.8 0.8 -2.2": ["tegen"], "4.6 0.8 12.6": ["nealry"], "14.0 10.5 14.0": ["metalers"], "8.0 -10.8 11.1": ["annnual"], "4.3 -6.0 3.1": ["incr"], "-0.7 18.0 5.0": ["inexplicit"], "2.3 9.3 7.3": ["hillslopes"], "10.6 6.1 10.8": ["slitters"], "3.3 6.8 4.7": ["departee"], "4.9 8.8 9.0": ["taxs"], "-1.4 -0.5 12.3": ["dicho"], "3.5 10.6 -1.9": ["politcally"], "4.7 13.9 8.0": ["syncretistic"], "9.9 9.3 10.5": ["gneissic"], "0.1 0.7 -0.6": ["finised"], "14.3 17.3 30.7": ["baitcasting"], "6.7 8.2 6.3": ["webware"], "9.7 9.0 12.3": ["warkaris"], "6.2 6.5 8.1": ["nunc"], "3.4 8.7 10.4": ["honge"], "-8.7 -0.8 -1.1": ["hypopituitarism"], "5.5 5.8 12.9": ["bilayers"], "-6.6 4.6 3.6": ["clinicopathological"], "-2.0 4.8 6.5": ["linearized"], "8.5 5.0 14.5": ["glycolipid"], "6.3 7.9 10.1": ["cocain"], "8.1 2.3 8.5": ["dib"], "14.1 5.7 12.1": ["dahn"], "4.0 10.7 7.8": ["hydroxides"], "7.3 13.2 27.1": ["nandinas"], "-2.1 13.7 9.0": ["milksop"], "7.7 17.8 1.7": ["demostrations"], "-0.5 4.5 4.4": ["evelopment"], "1.6 10.3 4.9": ["reacquaints"], "4.9 2.7 11.3": ["megakaryocytes"], "4.6 21.9 14.6": ["completionists"], "10.5 11.9 45.0": ["chowdah"], "3.4 8.2 13.3": ["originalsculptor"], "7.1 16.1 5.0": ["concatenate"], "5.9 21.9 18.2": ["pigweeds"], "3.7 5.5 2.7": ["deuterated"], "2.7 5.5 9.7": ["nonriders"], "-5.3 16.4 7.2": ["victime"], "1.3 13.2 5.4": ["barratry"], "22.9 6.9 10.1": ["afficianado"], "5.6 18.9 -0.3": ["securty"], "3.0 6.1 10.7": ["bacitracin"], "-5.8 10.6 4.5": ["normothermia"], "-1.3 3.0 16.9": ["cavas"], "14.0 8.2 12.2": ["underloved"], "25.4 16.7 31.6": ["maggoty"], "14.7 16.0 14.4": ["postcrisis"], "5.3 12.5 15.7": ["distrubing"], "7.2 11.3 10.6": ["metabolises"], "8.0 10.1 12.7": ["skimpily"], "2.8 25.2 6.0": ["atman"], "2.0 8.7 -1.8": ["saing"], "0.8 6.4 7.8": ["lila"], "9.5 7.0 14.7": ["damiana"], "17.7 10.8 7.1": ["screenfuls"], "0.7 3.6 9.2": ["jas"], "7.4 16.9 18.4": ["mulattoes"], "8.1 -2.3 8.8": ["bonused"], "2.1 4.6 -2.5": ["professionaly"], "6.1 6.8 7.0": ["electon"], "-1.5 -1.1 9.1": ["gastrostomy"], "14.5 21.2 7.7": ["flics"], "1.7 22.5 6.8": ["reequip"], "7.5 5.7 7.0": ["microstrip", "texto"], "-0.1 1.3 5.6": ["devant"], "12.9 5.0 13.7": ["celebri"], "15.2 18.4 20.8": ["noodler"], "7.2 11.4 11.3": ["beadle"], "16.1 11.8 19.0": ["cryptochromes"], "1.3 19.4 13.7": ["defogging"], "20.6 10.9 15.0": ["looooooong"], "2.6 -3.3 -4.2": ["hird"], "1.1 2.5 6.0": ["methylphenidates"], "-2.7 10.8 3.4": ["recuit"], "7.6 7.3 9.4": ["recontextualize"], "1.8 19.5 20.5": ["rhumbline"], "-0.0 0.9 -3.3": ["neuropsychopharmacology"], "4.3 -0.3 5.4": ["trainset"], "8.7 -3.3 6.6": ["upcycles"], "-6.3 -7.6 -2.1": ["colleted"], "7.5 14.7 18.2": ["skitching"], "9.0 -0.9 18.3": ["sampaguita"], "0.5 14.7 3.4": ["conterminous"], "8.4 11.4 12.1": ["unaccented"], "10.9 3.6 11.1": ["kerbweight"], "2.4 2.5 11.4": ["kanta"], "21.2 17.7 15.2": ["monocled"], "5.4 8.4 8.4": ["erat", "erodible"], "5.9 1.9 12.2": ["craniosacral"], "5.9 11.2 1.4": ["firefigher"], "3.7 7.1 5.5": ["carbene"], "8.3 4.3 12.6": ["phulkari"], "1.0 4.9 14.2": ["cabaletta"], "17.7 4.8 18.4": ["mochaccino"], "4.8 5.8 25.2": ["kiki"], "9.1 27.1 9.4": ["begums"], "6.9 15.7 8.9": ["vaporisation"], "6.8 24.1 11.3": ["uncultivable"], "11.0 3.4 12.0": ["completa"], "14.9 4.8 18.9": ["promenaders"], "7.0 15.7 12.2": ["haversacks"], "0.1 2.9 15.3": ["cuvees"], "9.8 6.2 15.5": ["ectasy"], "7.3 12.2 6.4": ["unrepeated"], "11.7 -4.4 9.8": ["pavings"], "1.9 -3.9 9.7": ["sba"], "0.4 4.7 3.0": ["achance"], "5.8 -8.5 2.1": ["preregistering"], "16.1 17.1 4.2": ["disarranged"], "9.0 18.5 3.3": ["opinionators"], "12.9 -1.2 12.6": ["dingier"], "14.0 6.4 27.4": ["loukoumades"], "8.1 15.4 10.5": ["mullered"], "7.9 3.5 -3.2": ["doorstepped"], "7.8 11.2 10.9": ["satyagrahis"], "1.4 8.8 8.6": ["kenneth"], "2.7 3.6 5.0": ["swamijis"], "8.9 7.4 6.3": ["wak"], "10.0 14.4 6.1": ["spywitness"], "9.0 13.1 11.0": ["netballing"], "2.5 5.0 4.8": ["outsprints"], "9.1 -0.7 20.2": ["kraftliner"], "-1.2 7.8 -1.5": ["persepctive"], "-7.5 8.8 4.3": ["nonpolice"], "21.6 30.4 12.9": ["plowshare"], "5.2 3.9 9.8": ["heatmaps"], "3.8 14.4 6.0": ["altsounds"], "8.4 6.6 16.5": ["disa"], "-2.1 9.7 3.1": ["mebers"], "7.4 13.1 3.5": ["aiports"], "0.6 4.8 10.8": ["lipopeptides"], "4.5 11.3 11.6": ["cloudmatt"], "0.2 10.4 1.0": ["irrevocability"], "12.5 -8.2 8.6": ["restrospective"], "2.2 19.3 9.3": ["boneheadedness"], "11.7 12.3 10.6": ["caravillas"], "10.4 12.6 14.3": ["ovah"], "16.1 2.4 22.6": ["shirring"], "2.6 7.3 1.9": ["desc"], "2.5 9.3 15.7": ["yai"], "-10.7 8.8 3.8": ["recontacted"], "15.2 17.4 21.5": ["fatass"], "2.4 13.3 13.6": ["sabras"], "-2.0 -1.8 3.4": ["appearnce"], "-4.1 3.3 9.9": ["kepada"], "9.9 4.0 22.1": ["dle"], "-1.6 7.6 9.3": ["comunidade"], "0.0 6.1 12.2": ["pulitika"], "15.7 12.0 10.7": ["microcantilever"], "11.0 18.8 18.4": ["baduk"], "16.4 14.7 26.1": ["chlorosomes"], "28.3 12.6 21.7": ["clawlike"], "20.7 13.5 11.7": ["braun"], "16.3 15.6 13.8": ["tweeness"], "-2.0 14.5 6.8": ["preponderate"], "-2.4 4.6 6.0": ["saida"], "-1.8 5.0 13.6": ["uncertaintly"], "11.1 2.9 11.1": ["smellies"], "10.1 13.5 12.7": ["streetballer", "nonparticipant"], "1.6 10.0 13.3": ["lowside"], "9.5 19.6 0.7": ["rethoric"], "3.7 10.8 9.6": ["raju"], "4.2 4.2 9.5": ["flowsheets"], "9.4 12.4 1.3": ["tranmission"], "8.9 2.7 12.5": ["nac"], "11.0 27.7 0.1": ["archfoes"], "-4.1 9.9 12.9": ["rechallenge"], "2.5 4.8 6.2": ["humaine"], "6.4 6.6 22.3": ["playboating"], "11.6 6.9 37.8": ["machaca"], "8.6 18.5 13.3": ["helitanker"], "9.3 7.8 46.0": ["steelheads"], "-0.1 20.3 10.8": ["crashingly"], "-6.6 10.4 3.8": ["shlita"], "-1.7 5.6 4.8": ["locknuts"], "7.3 2.2 5.1": ["primero"], "19.3 20.3 3.6": ["unnoticeably"], "12.1 14.1 13.9": ["bloused"], "7.9 9.3 24.1": ["medflies"], "4.2 12.2 -4.4": ["arrrest"], "4.5 2.2 15.9": ["hydroxytyrosol"], "7.5 0.6 17.5": ["silverwork"], "4.0 15.9 7.0": ["buttstock"], "3.3 -0.1 9.5": ["wic"], "22.0 2.6 14.2": ["replumbing"], "-2.0 8.5 10.6": ["foilists"], "-10.2 0.6 17.5": ["bienniums"], "1.5 13.5 14.0": ["bahasa"], "8.3 -2.6 -0.8": ["benjothaha"], "5.8 8.6 49.3": ["sandeel"], "6.0 10.5 12.6": ["desex"], "12.1 29.6 14.8": ["antisatellite"], "2.5 12.7 11.0": ["glaciological"], "-0.7 7.8 5.2": ["woould"], "5.1 4.2 2.6": ["incompleted"], "-1.8 14.1 4.3": ["biotechnologically"], "6.6 7.9 11.7": ["enrapt"], "12.7 3.0 15.9": ["acerage"], "16.4 0.3 -4.0": ["sublessor"], "6.7 4.2 7.2": ["intenational"], "21.2 8.3 13.5": ["berber"], "1.9 10.2 11.4": ["osteochondroma"], "-5.7 7.2 0.7": ["transactionally"], "16.5 7.8 37.6": ["raviolo"], "-0.1 14.5 17.7": ["fusspot"], "3.9 23.4 10.5": ["individuate"], "10.6 15.2 12.4": ["irfan"], "7.2 10.5 15.6": ["enim"], "4.2 8.1 13.8": ["bete"], "8.7 4.6 48.9": ["nephrops"], "10.1 8.5 23.1": ["photogram"], "2.4 -3.6 10.1": ["publicworks"], "9.9 9.4 17.9": ["nippled"], "13.1 5.3 53.8": ["baywide"], "1.6 7.8 0.4": ["dysgraphia"], "5.4 20.8 6.4": ["engagers"], "9.3 14.0 27.0": ["gimlets"], "-5.0 0.5 19.2": ["raan"], "5.7 3.9 2.8": ["desig"], "0.9 10.4 12.5": ["undocumenteds"], "9.7 16.3 15.2": ["smackhead"], "15.0 2.1 11.6": ["docksides"], "-6.9 9.8 4.8": ["estramustine"], "15.3 14.0 21.2": ["wafty"], "1.7 15.7 10.8": ["tose"], "-4.6 16.0 12.7": ["curability"], "7.1 3.0 8.2": ["unretires"], "13.1 3.8 3.6": ["zdnet"], "5.9 17.7 5.2": ["retarted"], "19.5 27.9 29.6": ["goomba"], "3.9 13.2 7.2": ["couped"], "-8.7 -1.3 2.7": ["relicensure"], "-7.8 25.4 3.2": ["officered"], "7.6 12.0 6.6": ["biochem"], "2.2 11.8 21.2": ["amaro"], "1.6 12.9 12.7": ["marcos"], "8.2 4.2 7.8": ["sidebags"], "15.4 2.4 20.3": ["sunray"], "-12.4 6.5 3.9": ["narrowbanding"], "13.1 13.8 7.4": ["orientates"], "5.4 36.2 5.5": ["warhawks"], "20.7 34.2 19.5": ["battlecruiser"], "7.8 10.0 21.4": ["fizziness"], "-2.3 16.5 0.1": ["kabbalists"], "11.1 2.7 7.4": ["candelight"], "6.5 10.5 11.6": ["nanoribbon"], "10.5 27.1 5.7": ["shitheads"], "-8.3 10.2 10.2": ["suf"], "11.8 0.1 5.4": ["nanomedical"], "3.9 -2.2 7.1": ["organi"], "7.0 8.1 1.0": ["metropolitian"], "-9.1 -4.5 8.3": ["cocurricular"], "3.2 2.4 13.8": ["buba"], "9.2 20.1 3.3": ["dishonourably"], "22.5 16.5 28.6": ["wienie"], "2.4 8.1 7.6": ["hemorrhoidal"], "3.7 7.0 15.0": ["leys"], "8.7 11.9 6.5": ["ufologist"], "-0.1 -3.7 -0.1": ["internationales"], "12.2 5.1 29.4": ["banku"], "6.7 8.4 5.2": ["trabajadores"], "6.2 12.6 9.0": ["numpad"], "0.2 8.7 -1.4": ["thatt"], "10.4 7.7 14.3": ["indoles"], "13.5 7.8 -3.9": ["strenthen"], "0.1 5.8 3.1": ["monophasic"], "5.6 10.0 15.6": ["undereating"], "9.1 17.6 15.8": ["suckerpunch"], "10.3 17.8 24.7": ["monarda"], "3.5 15.8 3.0": ["indiviual"], "16.8 16.3 16.7": ["guvnor"], "7.7 14.9 9.0": ["platteland"], "12.3 10.0 3.9": ["miscalibrated"], "8.6 7.9 26.4": ["primula"], "-6.3 20.0 13.4": ["malarious"], "-1.7 1.4 1.9": ["cancellable"], "8.2 17.1 6.6": ["syrian"], "4.0 9.5 20.1": ["unke"], "-7.3 3.5 5.7": ["enrolees"], "-0.1 19.9 -5.5": ["mily"], "-3.9 11.2 10.8": ["hia"], "7.6 -2.0 15.4": ["plumpish"], "13.0 12.5 4.4": ["millenial"], "-0.4 11.1 16.8": ["asin"], "12.6 3.1 24.6": ["nile"], "-5.3 1.6 15.8": ["umbers"], "10.5 8.5 9.0": ["schlager"], "5.5 -0.5 2.7": ["releaed"], "8.1 6.7 22.6": ["sluiceway"], "10.9 -4.8 10.9": ["descrambler"], "9.7 -0.2 -1.1": ["anddevelopment"], "14.5 4.8 11.6": ["resculpted"], "2.6 9.5 12.5": ["arah"], "3.1 6.9 13.1": ["pressurizer"], "3.8 6.8 10.8": ["retrotransposon"], "12.4 2.1 15.4": ["speedskate"], "7.2 18.5 9.2": ["selfconfidence"], "-1.6 3.8 4.6": ["entitiled"], "2.2 8.8 7.9": ["dimished", "carbonyls"], "2.5 15.4 12.4": ["junkballer"], "1.8 10.3 12.5": ["isu"], "-0.6 4.4 4.2": ["treelined"], "11.9 10.8 14.6": ["muling"], "-0.8 5.7 -0.4": ["sleevenotes"], "-1.9 20.3 6.7": ["belli"], "10.3 -2.0 -1.4": ["officed"], "7.5 3.2 12.5": ["myung"], "-6.2 1.9 0.1": ["detergency"], "2.0 8.8 15.4": ["kula"], "11.5 7.0 4.1": ["commerically"], "1.3 13.2 12.5": ["muerte"], "16.5 -0.8 0.8": ["broadliner"], "12.0 7.3 32.5": ["mamey"], "16.3 2.9 10.5": ["cheekboned"], "5.1 16.8 0.4": ["reintegrates"], "4.7 1.9 5.0": ["hryvnya"], "17.7 13.5 0.9": ["exibit"], "18.4 12.2 12.8": ["groundsheet"], "4.4 20.0 4.0": ["polygraphers"], "27.5 1.7 11.9": ["tweeny"], "1.4 4.9 2.6": ["currentexpectations"], "4.4 8.1 4.9": ["enkephalin"], "-0.9 0.4 -8.5": ["referal"], "12.6 5.9 13.5": ["narghile"], "11.4 6.7 11.9": ["chuggin"], "13.6 4.5 24.6": ["bialys"], "12.0 -0.2 3.8": ["innesota"], "4.3 -7.7 7.8": ["metallizing"], "3.2 6.0 14.7": ["comprende"], "8.3 9.0 13.6": ["tripolar"], "2.6 8.2 1.7": ["handballer"], "-0.3 -2.6 3.0": ["polyposis"], "5.6 10.9 20.5": ["muscatel"], "13.5 -5.8 4.5": ["rth"], "13.2 18.2 12.3": ["sizewise"], "2.6 16.7 19.1": ["nematicides"], "9.3 0.3 13.9": ["voiles"], "-0.2 4.2 8.1": ["aime"], "19.7 8.2 31.2": ["caul"], "13.3 15.8 1.4": ["gleek"], "14.9 1.9 -3.8": ["ustwo"], "-2.6 5.0 9.2": ["hypogonadal"], "16.0 10.7 22.5": ["daggerboards"], "26.1 12.3 9.5": ["toymaking"], "0.7 2.0 9.2": ["headshops"], "26.9 6.0 19.4": ["dropcloth"], "5.2 31.1 3.1": ["desecrators"], "9.3 4.8 5.6": ["beste"], "11.8 2.4 13.7": ["sna"], "-7.1 -3.6 7.5": ["studnets"], "0.7 1.5 14.6": ["jien"], "8.3 8.8 8.5": ["stre"], "1.9 2.2 10.3": ["garrett"], "4.1 3.4 9.6": ["gtk"], "-3.1 14.9 12.8": ["crystallin"], "15.6 15.2 28.1": ["arborvitaes"], "12.3 10.6 12.6": ["southtowns"], "4.0 2.2 13.1": ["midbass"], "14.0 19.4 10.7": ["econmy"], "0.6 -3.1 17.2": ["soe"], "-4.6 6.4 7.2": ["curium"], "15.4 11.1 13.7": ["untenanted"], "3.3 22.8 13.3": ["lieth"], "1.2 12.8 10.5": ["hattricks"], "12.3 4.1 17.2": ["aequorin"], "12.3 6.8 7.3": ["embossment"], "5.1 18.4 13.7": ["blockhole"], "8.3 10.3 17.6": ["tearin"], "12.0 9.9 3.6": ["unburdens"], "-2.8 -3.3 3.6": ["presenation"], "7.8 11.0 11.8": ["lineball"], "3.6 2.1 5.8": ["viscoelastics"], "13.6 11.1 5.7": ["plosive"], "18.8 -0.5 -0.6": ["transistorized"], "9.8 3.7 0.1": ["videotelephony"], "-1.8 0.5 -3.5": ["tvsdesign"], "11.7 13.9 16.8": ["perspectival"], "-5.4 2.2 2.7": ["remorsefulness"], "9.0 3.4 7.0": ["soos"], "14.6 12.4 14.7": ["bearding"], "13.8 12.7 6.4": ["oles"], "-0.9 9.2 1.8": ["dehydrogenation"], "4.5 22.5 0.7": ["vilifications"], "-0.6 3.4 7.0": ["vertebras"], "-11.8 2.7 4.1": ["podiumed"], "12.6 4.5 3.9": ["songsheet"], "9.1 18.7 13.6": ["pettier"], "13.8 11.0 16.8": ["miniblinds"], "5.4 14.5 7.5": ["vhd"], "8.9 -3.7 11.9": ["midweight"], "9.6 1.2 8.9": ["watersupply"], "5.1 2.6 2.2": ["qualy"], "5.8 5.4 3.1": ["radeon"], "8.5 17.5 11.4": ["francophile"], "20.1 21.7 36.8": ["wrigglers"], "10.6 13.1 31.0": ["balangay"], "2.4 0.6 3.5": ["papaverine"], "1.9 6.0 3.2": ["encapsulations"], "2.9 1.6 4.1": ["todas"], "18.0 17.9 11.8": ["placemark"], "-8.3 5.1 -0.1": ["finishe"], "14.0 0.8 8.1": ["launderettes"], "18.8 1.8 7.6": ["parp"], "10.5 2.8 14.4": ["buick"], "7.4 14.3 21.0": ["masiao"], "10.5 9.3 23.4": ["grasscloth"], "3.4 10.0 7.4": ["cryopyrin"], "1.1 4.0 -7.8": ["toldthe"], "8.4 26.6 8.2": ["vassalage"], "-1.7 18.1 -5.4": ["innaccurate"], "6.5 5.6 12.0": ["nonplayers"], "3.8 2.6 20.3": ["greatgrandmother"], "13.2 29.0 2.1": ["libyan"], "3.1 4.3 4.5": ["lipopeptide"], "-4.3 -5.5 5.3": ["aad"], "2.7 16.8 18.5": ["oversliding"], "-6.4 14.4 5.2": ["bogosi"], "-2.9 2.6 13.9": ["sudah"], "1.0 10.9 5.4": ["visitable"], "2.5 -5.1 8.4": ["presen"], "14.7 3.0 20.5": ["swarovski"], "11.4 4.0 25.2": ["batu"], "15.9 19.6 14.8": ["unblessed"], "6.4 -3.9 5.1": ["bens"], "5.8 5.6 15.1": ["nontitle"], "10.9 5.4 28.6": ["shawarmas"], "10.9 10.9 13.5": ["cutey"], "4.9 2.3 0.7": ["fule"], "7.6 10.6 1.8": ["aspirationally"], "14.2 7.0 20.9": ["horehound"], "0.1 18.8 9.0": ["luridness"], "13.0 24.3 27.8": ["mountainman"], "-0.7 3.0 -0.4": ["zaleplon"], "1.9 18.6 2.1": ["lase"], "10.2 8.0 21.9": ["rockhounds"], "-7.2 -1.6 8.4": ["prepatory"], "5.7 11.4 11.6": ["deshi"], "9.4 6.1 12.6": ["babymaking"], "9.1 12.1 18.2": ["celestially"], "-2.1 11.5 9.5": ["clostridial"], "-0.0 8.0 10.1": ["debride"], "7.3 32.3 9.3": ["roguelike"], "14.7 11.8 29.6": ["rucola"], "16.2 8.8 20.5": ["biffs"], "13.5 11.1 14.5": ["fireboxes"], "2.7 7.2 10.0": ["podemos"], "24.7 24.2 26.2": ["battening"], "7.0 7.6 12.3": ["minitruck"], "11.4 9.4 3.3": ["turbopumps"], "-1.6 11.1 11.4": ["curanderos"], "1.7 8.3 17.5": ["magar"], "0.8 7.8 23.9": ["nanay"], "4.7 11.5 7.3": ["reparing"], "9.9 11.3 15.5": ["boomeritis"], "7.6 15.9 11.8": ["whenver"], "9.0 5.9 11.0": ["gaadi"], "-0.4 1.9 7.7": ["pends"], "7.8 20.3 11.4": ["socializer"], "5.4 0.1 6.9": ["amelia"], "-4.1 8.7 8.7": ["alefacept"], "14.7 3.9 -1.5": ["pipleline"], "6.3 10.9 -2.0": ["concretizing"], "8.2 15.1 17.5": ["unbossed"], "13.1 21.7 17.9": ["milquetoasts"], "11.5 4.8 19.2": ["dustcarts"], "4.0 19.6 11.5": ["sidebands"], "-5.7 3.8 11.8": ["unofficials"], "0.5 -5.9 -1.6": ["cleverbridge"], "4.4 2.8 23.7": ["ferrymen"], "11.8 19.2 9.0": ["spatiality"], "4.6 -7.6 -6.1": ["cohead"], "10.4 12.6 39.3": ["scaloppini"], "-1.4 -0.5 4.4": ["mezzosoprano"], "2.6 13.0 11.4": ["baseballgirl"], "2.3 0.7 12.4": ["jubilarians"], "4.7 17.7 4.2": ["enflames"], "11.0 5.6 -1.1": ["specialy"], "-0.8 0.5 6.3": ["juge"], "-7.8 12.5 -1.8": ["surahs"], "12.0 2.5 32.4": ["souper"], "-6.9 2.4 3.2": ["infomration"], "2.8 4.1 10.2": ["hafna"], "-1.9 11.1 16.5": ["bargirls"], "-0.0 22.7 8.8": ["belligerant"], "11.9 11.1 13.7": ["laydee"], "5.8 9.3 12.4": ["mabye"], "4.4 11.2 7.0": ["overactivation"], "7.9 9.1 16.0": ["khaini"], "-2.4 9.8 13.6": ["masama"], "11.7 4.3 2.1": ["privatesector"], "0.2 7.7 13.3": ["jaldi"], "7.1 -7.3 9.6": ["reit"], "7.2 7.8 14.6": ["etting"], "0.4 23.0 11.4": ["cav"], "-8.7 6.2 6.2": ["pentoxifylline"], "0.2 11.6 6.1": ["girlfirend"], "4.1 14.0 9.5": ["lickings"], "16.2 4.8 10.3": ["handcar"], "8.7 23.1 6.9": ["sulker"], "8.5 1.9 17.9": ["portraitures"], "6.7 10.0 10.8": ["superclasico"], "13.9 8.5 18.4": ["palletize"], "1.0 8.5 3.0": ["endobronchial"], "18.1 12.6 15.3": ["shammy"], "15.8 -2.6 1.7": ["roup"], "7.6 8.1 32.3": ["syllabub"], "1.8 6.5 14.5": ["phototransistor"], "8.5 15.2 10.0": ["wackadoo"], "11.6 7.8 7.6": ["infantswear"], "-5.7 1.6 -8.0": ["rbb"], "-4.8 14.7 5.2": ["grimalot"], "13.3 13.4 11.1": ["pikeys"], "11.0 8.9 5.6": ["photoelectron"], "11.7 6.8 11.6": ["taches"], "8.7 16.2 7.1": ["graffitists"], "8.3 6.3 17.8": ["minitrucks"], "1.2 14.1 8.3": ["headwork"], "8.4 -4.8 13.0": ["frameable"], "4.0 15.8 10.5": ["misbalance"], "2.5 8.5 8.7": ["thorughout"], "11.9 9.8 11.3": ["racketing"], "-3.1 12.0 7.8": ["effacement"], "7.5 2.9 33.6": ["garlics"], "20.1 10.1 25.0": ["ribbit"], "15.4 13.7 14.2": ["stropped"], "6.1 19.4 6.8": ["impressionistically"], "5.8 0.2 0.0": ["reimaged"], "6.7 3.9 16.2": ["buffo"], "3.5 18.4 7.6": ["sheroes"], "9.5 8.3 12.1": ["betamax"], "6.8 8.3 17.0": ["parksandrec"], "8.4 12.4 10.6": ["histor"], "5.2 -6.4 4.6": ["settembre"], "-0.5 15.5 15.7": ["playgoer"], "-0.6 10.6 6.5": ["titleless"], "4.1 23.3 -0.7": ["bullnecked"], "-0.2 10.8 8.9": ["kontrabida"], "-2.2 4.7 7.8": ["enda"], "4.8 14.3 4.5": ["atitude"], "3.5 12.6 7.0": ["thnx"], "-1.3 14.2 8.6": ["touchwood"], "-2.7 13.8 13.3": ["arabinose"], "9.2 7.2 24.2": ["dachsund"], "16.6 4.1 7.0": ["flambouyant"], "12.6 4.9 2.6": ["wayback"], "-11.9 2.6 -0.8": ["nonadherent"], "10.3 9.0 10.9": ["carlton"], "16.1 10.7 16.8": ["hoopty"], "11.9 11.8 9.8": ["stuntwomen"], "13.7 10.8 24.4": ["sponson"], "14.0 9.0 -2.9": ["strongarmed"], "2.4 6.9 21.3": ["balita"], "8.8 3.4 11.8": ["mrc"], "0.9 15.6 8.9": ["probem"], "9.1 18.8 7.2": ["vapidly"], "6.0 5.3 4.4": ["polymathic"], "-5.0 -6.5 -0.8": ["sportskool"], "10.6 12.1 2.2": ["kenyan"], "-1.2 -0.3 3.7": ["unitedstreaming"], "-4.7 -3.9 5.9": ["weeke"], "10.3 -4.8 11.7": ["noncasino"], "8.0 6.3 18.4": ["sagar"], "0.2 8.6 6.4": ["recurrance"], "8.8 1.9 2.6": ["tokenless"], "12.7 15.3 7.1": ["voltmeters"], "1.3 3.6 5.8": ["smp"], "5.0 6.8 16.4": ["dresscode"], "-3.1 8.9 6.4": ["forecaddie"], "-5.1 9.4 9.9": ["lapsation"], "20.9 12.4 8.7": ["tumblin"], "-0.7 6.5 7.7": ["komatiites"], "17.6 13.4 5.5": ["esk"], "2.2 3.1 7.6": ["aneurysmal"], "1.1 -0.4 8.2": ["eprodisate"], "2.5 8.7 16.2": ["togging"], "1.0 -8.3 -3.1": ["multisession"], "10.1 32.7 3.1": ["barbarisms"], "3.3 1.6 6.3": ["descramblers"], "4.8 20.6 10.0": ["incumbencies"], "10.4 3.0 11.3": ["merchandized"], "7.3 29.6 3.1": ["unstopable"], "5.8 4.9 1.1": ["allegely"], "8.3 10.0 16.2": ["siping"], "3.9 11.7 24.7": ["bioblitz"], "4.6 9.6 9.5": ["medinas"], "6.8 12.0 11.7": ["blackbody"], "13.0 9.3 2.7": ["businesman"], "2.9 16.0 13.1": ["kidd"], "-5.0 3.7 2.9": ["nanoeconomics"], "6.5 -0.2 12.4": ["caseins"], "22.9 7.3 13.4": ["trashbags"], "15.1 17.0 33.1": ["sapsuckers"], "5.5 3.5 12.3": ["gazettal"], "4.6 10.6 25.3": ["vegetatively"], "-0.9 17.7 12.7": ["rollickings"], "5.3 13.8 11.1": ["subscirbe"], "5.2 8.8 11.7": ["pasos"], "16.0 7.7 13.4": ["ticky"], "1.9 -1.9 3.8": ["changesin"], "13.8 5.8 13.7": ["achey"], "27.7 3.5 7.1": ["plaform"], "3.6 19.1 16.2": ["cheapshots"], "10.6 15.0 12.2": ["garbages"], "2.6 14.6 18.1": ["malcolm"], "-6.7 7.4 11.8": ["tebuconazole"], "15.8 14.0 10.2": ["yutz"], "22.2 16.0 35.0": ["griffon"], "7.1 12.8 9.8": ["chloe"], "-2.9 1.0 0.8": ["impr"], "2.0 12.7 -3.7": ["subsquent"], "-6.3 1.1 13.0": ["overenrolled"], "10.9 13.9 14.6": ["tightfistedness"], "7.4 2.0 -2.3": ["enetered"], "8.0 10.9 2.9": ["crossbuck"], "-3.8 -7.2 2.5": ["concertmasters"], "-2.3 14.8 2.9": ["biopreparedness"], "9.0 13.7 12.3": ["ubersexual"], "15.3 1.9 11.0": ["noiseniks"], "5.7 0.3 10.6": ["resminostat"], "16.2 15.9 33.5": ["bobhouse"], "2.3 8.1 11.0": ["quiltmakers"], "11.7 7.9 21.4": ["puka"], "6.1 16.0 19.0": ["marvin"], "17.4 -0.9 1.3": ["informaticians"], "0.8 5.9 9.4": ["selectboards"], "4.1 7.7 18.8": ["hoos"], "20.6 8.4 3.2": ["excutives"], "7.0 -5.3 21.4": ["vins"], "8.3 2.1 21.0": ["swizzle"], "6.1 4.4 20.2": ["biglang"], "3.3 -8.0 1.7": ["chm"], "8.2 -3.5 7.2": ["zoomers"], "6.0 7.6 9.2": ["anim"], "-0.7 4.9 11.6": ["kurtosis"], "8.2 12.9 11.2": ["gladder"], "9.8 22.2 6.2": ["governements"], "5.7 5.8 9.5": ["resignalling"], "17.0 18.9 16.3": ["bejeesus"], "-6.3 -1.4 5.3": ["passsed"], "0.3 6.3 12.6": ["tisanes"], "-3.4 7.3 13.2": ["hydrographer"], "7.7 2.5 21.8": ["unshorn"], "2.1 0.2 5.4": ["jauntier"], "5.7 -1.4 7.0": ["quasquicentennial"], "5.0 6.8 10.2": ["meningeal"], "-5.9 4.0 4.6": ["microwatt"], "6.2 11.1 9.3": ["behavious"], "-2.6 4.3 6.8": ["doubledouble"], "15.9 7.1 4.8": ["fructifying"], "10.0 16.5 24.0": ["forewings"], "2.2 9.1 20.7": ["suka"], "26.1 -2.0 -3.9": ["moghul"], "3.3 7.5 15.6": ["dogtrot"], "6.3 9.5 18.1": ["maquillage"], "8.0 10.5 8.9": ["distending"], "9.1 18.4 4.3": ["aviations"], "6.4 -0.1 3.3": ["enteropathy"], "7.7 10.0 8.2": ["flagrancy"], "4.9 15.8 9.6": ["divadom"], "4.5 15.6 12.7": ["feverously"], "6.1 5.2 12.7": ["camden"], "9.6 1.9 9.4": ["apenas"], "9.9 5.8 9.0": ["malouda"], "10.8 19.9 7.0": ["harries"], "23.4 5.0 11.1": ["drapped"], "12.9 8.9 25.2": ["sunnyside"], "-0.2 27.7 1.9": ["terrorisation"], "8.0 11.5 9.9": ["winnig"], "4.3 6.1 13.4": ["moder"], "0.5 15.1 7.0": ["roadbook"], "7.0 21.8 7.2": ["defriending"], "-1.9 10.4 11.8": ["unneccessarily"], "7.3 24.2 11.5": ["depowered"], "0.1 11.0 8.6": ["comeing"], "3.0 2.9 11.1": ["radiolabeling"], "8.4 3.0 19.6": ["surplice"], "4.8 18.8 10.2": ["filoviruses"], "4.5 7.8 12.2": ["myelinated"], "-5.8 -3.1 6.9": ["mcfpd"], "2.5 0.3 18.9": ["malaki"], "-3.4 15.7 6.4": ["hypochondriasis"], "15.9 17.3 14.5": ["leadfoots"], "12.4 6.1 -0.1": ["peacebroker"], "8.4 3.6 5.4": ["railfreight"], "0.7 17.4 2.1": ["confort"], "13.6 4.4 22.9": ["marge"], "5.2 1.8 2.7": ["droxidopa"], "18.6 13.0 10.9": ["phlegmatically"], "1.3 16.6 8.3": ["proabably"], "6.2 10.6 5.9": ["residuum"], "12.3 9.7 16.2": ["phenolphthalein"], "0.5 33.1 6.7": ["civilan"], "9.4 9.2 -0.2": ["pdas"], "15.8 18.1 7.4": ["hyperbolized"], "-0.3 11.1 19.2": ["malakas"], "8.7 8.8 30.3": ["beefiness"], "0.8 15.2 9.3": ["beanings"], "-5.5 -0.5 5.3": ["requried"], "4.6 4.9 7.7": ["supermiddle"], "4.9 -0.2 25.3": ["pescatarian"], "5.1 -2.6 6.6": ["originially"], "-1.2 16.6 7.4": ["bacha"], "12.5 5.9 27.2": ["yeasted"], "5.7 10.3 7.1": ["invadopodia"], "-1.2 7.3 14.2": ["hepatoma"], "16.3 3.5 9.9": ["megatonne"], "-0.4 14.0 6.8": ["separationist"], "-0.1 10.7 7.8": ["verteran"], "13.3 8.5 4.0": ["suburbans"], "-1.9 -4.7 0.8": ["collegewide"], "1.9 4.1 -1.5": ["nicotinic"], "14.8 19.4 24.9": ["cranesbill"], "9.3 4.9 21.7": ["taki"], "12.2 11.6 13.1": ["indefinably", "transportational"], "15.0 0.6 -0.1": ["servicesto"], "7.7 33.0 3.6": ["traitorously"], "1.9 10.7 4.6": ["disestablishing"], "-1.0 10.5 10.4": ["threescore"], "-0.4 1.8 3.2": ["tenorist"], "6.2 11.4 7.0": ["cheerers"], "28.4 15.3 20.5": ["beasty"], "-6.2 5.4 7.3": ["asissts"], "15.1 -1.5 17.9": ["kroners"], "7.4 -6.6 -2.1": ["sulfonate"], "1.1 9.9 22.4": ["baladi"], "-1.6 1.5 12.3": ["annualizes"], "3.5 8.7 3.1": ["folkloristic"], "-5.6 13.8 3.4": ["unappointed"], "3.2 11.3 4.0": ["suppost"], "10.2 5.6 3.6": ["recapitalizes"], "3.5 -4.6 5.7": ["meticals"], "11.0 12.3 19.5": ["beachbreaks"], "4.5 3.2 15.2": ["cartes"], "0.3 1.7 13.5": ["healthspan"], "12.2 25.0 3.6": ["fiercly"], "17.0 -1.0 10.8": ["planto"], "7.3 24.1 5.2": ["escapable"], "16.8 15.7 7.9": ["jailbreaker"], "10.0 13.7 17.1": ["cholos"], "17.6 16.0 41.4": ["spatchcock"], "8.1 19.5 16.0": ["jobbery"], "-2.4 9.6 15.3": ["rehris"], "11.1 18.4 9.5": ["buch"], "2.2 -5.0 -1.0": ["relatedto"], "21.4 10.5 25.5": ["daintiest"], "12.5 1.0 28.8": ["saucisson"], "-0.1 10.6 4.1": ["goniometer"], "1.4 8.0 8.0": ["rebroke"], "3.8 6.2 9.1": ["sportstalk"], "5.9 2.3 27.2": ["bushiness"], "13.3 22.0 14.0": ["launchable"], "10.9 9.3 35.5": ["pickleweed"], "12.2 8.4 6.9": ["squandermania"], "15.2 12.1 17.3": ["clownishly"], "17.6 17.8 2.8": ["spinmasters"], "12.5 10.5 21.4": ["pieris"], "3.0 8.6 7.9": ["texte"], "15.9 3.4 10.2": ["macy"], "1.5 19.7 10.7": ["pollers"], "1.5 42.7 -0.6": ["mujahed"], "11.6 10.1 -2.3": ["moralisation"], "-0.3 26.9 12.1": ["ethnocentricity"], "3.8 10.9 3.1": ["misiones"], "2.1 20.9 15.2": ["manyattas"], "9.9 30.5 3.3": ["hellishness"], "-6.2 2.6 -2.0": ["tetraplegia"], "15.0 4.3 5.8": ["staion"], "-6.4 12.3 0.4": ["scouter"], "2.7 4.3 14.8": ["blueways"], "1.2 8.2 12.9": ["autosomes"], "-4.8 10.4 0.5": ["firstand"], "9.7 0.5 15.4": ["linn"], "5.2 25.5 6.3": ["hagiographers"], "29.0 5.6 14.4": ["tinseled"], "0.3 11.8 9.3": ["perpetuities"], "16.8 14.1 5.0": ["bunkerlike"], "2.6 7.4 13.3": ["nakikita"], "8.8 8.4 19.8": ["serviceberries"], "0.8 7.6 7.9": ["supersedeas"], "9.2 8.1 26.0": ["overplanting"], "3.4 11.7 -4.6": ["authourities"], "4.7 3.8 8.0": ["trendspotters"], "11.5 3.3 15.2": ["stee"], "4.5 16.7 17.5": ["overtops"], "5.7 5.9 29.2": ["gallinules"], "5.1 9.6 10.1": ["pedestrain"], "-2.9 16.8 0.7": ["critisizing"], "-7.2 22.9 4.2": ["primaried"], "10.4 19.5 10.0": ["experence"], "9.9 -5.2 8.4": ["froom"], "15.9 -0.7 4.7": ["asmuch"], "9.0 0.3 10.5": ["forcemain"], "6.8 14.6 31.6": ["beechnuts"], "20.3 5.6 16.1": ["aglitter"], "10.9 10.7 29.4": ["chae"], "17.7 13.7 9.1": ["solarized"], "-7.1 6.2 2.2": ["repatriable"], "12.9 5.4 21.4": ["struvite"], "14.7 28.6 14.4": ["despoiler"], "22.8 12.7 3.5": ["vrooming"], "11.9 17.8 19.0": ["squawkers"], "8.3 0.9 13.8": ["kanjira"], "3.8 14.0 14.6": ["cardia"], "16.7 13.4 18.0": ["stuf"], "12.8 3.6 6.8": ["vidgames"], "5.0 17.7 5.9": ["tetchily"], "20.0 20.7 21.9": ["lizardlike"], "14.6 7.4 39.7": ["surgeonfish"], "11.4 21.2 19.3": ["changelings"], "0.9 -0.6 2.7": ["newsline"], "-0.8 0.8 12.5": ["kohanga"], "-4.0 11.7 10.0": ["upperweights"], "2.9 2.7 2.2": ["denuncia"], "-0.5 -6.5 5.7": ["cei"], "11.5 5.8 27.7": ["tuk"], "-1.1 -9.6 -8.2": ["diretor"], "5.9 9.6 9.3": ["headlice"], "10.4 7.6 8.9": ["swotted"], "8.0 5.4 5.3": ["oint"], "4.3 24.3 7.2": ["intransigency"], "5.7 8.7 12.8": ["listees"], "1.1 7.9 17.2": ["zarda"], "12.1 -6.2 16.8": ["architrave"], "7.6 11.4 8.7": ["rythmic"], "19.4 0.9 -3.2": ["technopolis"], "12.9 3.4 21.5": ["framboise"], "10.5 31.6 -2.5": ["contantly"], "12.0 11.3 14.8": ["quonset"], "5.6 2.4 18.3": ["nagawa"], "5.3 13.6 12.6": ["usedto"], "1.0 1.1 4.6": ["residen"], "10.9 -1.8 3.1": ["solars"], "3.6 -0.7 27.3": ["kulcha"], "-3.4 12.1 9.1": ["outfinish"], "-1.5 5.4 18.6": ["frizzante"], "3.3 4.5 29.3": ["starchier"], "2.6 6.4 6.0": ["radioembolization"], "-0.9 3.5 2.2": ["tul"], "16.0 -2.4 14.3": ["insurace"], "-1.2 16.4 7.3": ["scotfree"], "13.0 15.0 10.8": ["outgross"], "3.3 17.4 12.1": ["indios"], "8.0 -5.3 11.2": ["piasters"], "-4.3 19.2 -0.2": ["testifier"], "0.7 11.0 24.3": ["invertase"], "9.9 9.0 12.8": ["premesis"], "11.4 9.5 16.8": ["unsticking"], "2.0 8.2 11.6": ["hoasca"], "7.3 5.2 1.2": ["enterpreneurship"], "1.4 6.1 -2.4": ["unware"], "5.7 6.7 13.2": ["hydrometeorology"], "7.4 12.4 -2.5": ["headunit"], "2.6 14.5 16.1": ["vernier"], "14.7 11.0 10.1": ["percolators"], "19.3 20.9 11.9": ["beseechingly"], "13.0 13.5 24.2": ["hogshead"], "13.7 10.2 -0.4": ["dictaphones"], "8.0 7.0 8.9": ["autodialers"], "10.3 12.0 12.4": ["ickier"], "1.3 17.8 5.8": ["txting"], "9.1 11.4 22.9": ["touchers"], "19.4 9.8 32.1": ["spiderlings"], "17.4 14.1 21.8": ["tarlike"], "4.5 -2.6 10.1": ["nol"], "15.4 1.1 10.7": ["multigenre"], "5.4 -7.5 3.7": ["economie"], "-0.9 2.8 3.0": ["aplindore"], "4.3 11.2 4.3": ["overindebtedness"], "-0.2 10.1 9.6": ["stilbene"], "17.1 3.7 5.4": ["finallist"], "-9.7 1.1 1.9": ["enunciations"], "5.2 10.8 34.9": ["bassing"], "6.0 8.0 13.3": ["pentaprism"], "4.8 3.0 20.4": ["maizemeal"], "-5.7 16.1 16.5": ["kohanim"], "2.3 16.6 5.5": ["atelectasis"], "4.9 4.9 8.3": ["samt"], "17.1 6.4 14.8": ["stinko"], "1.8 -11.7 16.3": ["annaul"], "5.6 16.2 9.9": ["furanocoumarins"], "18.0 7.4 16.8": ["refrig"], "8.7 2.8 12.8": ["redhat"], "8.7 5.3 27.8": ["loganberry"], "-10.2 4.9 5.1": ["boardwork"], "20.1 14.7 23.6": ["cameltoe"], "6.3 13.5 12.7": ["nucleoli"], "25.7 7.2 17.7": ["biodome"], "-2.2 31.2 0.9": ["shaheeds"], "11.8 25.0 11.0": ["futureless"], "-3.6 4.2 1.0": ["electrophysiologic"], "11.1 23.0 17.5": ["putzes"], "3.6 -10.5 2.9": ["nka"], "-4.3 15.4 16.6": ["rythmn"], "8.2 -0.6 30.5": ["nyonya"], "12.8 11.6 10.0": ["anthracene"], "2.3 13.8 4.0": ["islanding"], "1.1 13.8 2.5": ["marjaiya"], "10.4 9.5 11.0": ["nixon"], "11.0 14.0 12.7": ["funsies"], "15.7 9.2 3.8": ["redtop"], "5.6 8.7 22.3": ["trapshooters"], "-3.8 12.0 6.2": ["sentencers"], "3.3 12.4 22.2": ["manamko"], "4.9 16.0 4.2": ["anticipative"], "-1.1 -6.2 9.2": ["accupuncture"], "5.0 8.0 3.3": ["orde"], "17.8 13.9 11.3": ["curare"], "22.5 11.4 12.8": ["protoplanet"], "2.8 6.8 12.8": ["cogitated"], "23.0 19.5 7.8": ["superstrength"], "15.2 9.6 29.0": ["nestbox"], "7.8 17.7 16.6": ["tonto"], "1.2 3.8 -3.0": ["officebearers"], "9.6 14.5 6.5": ["reknit"], "0.9 9.3 14.2": ["oka"], "0.8 10.2 4.2": ["phonemic"], "9.2 8.5 5.2": ["probems"], "5.9 2.4 10.9": ["genomewide"], "9.4 6.9 19.9": ["phytoliths"], "1.1 23.2 6.1": ["sainiks"], "7.4 11.9 1.8": ["uncomplicate"], "3.7 4.6 4.3": ["prevelance"], "-3.1 14.7 5.5": ["intermeddling"], "3.9 10.8 8.5": ["zim"], "1.9 12.4 10.9": ["ejdionne"], "13.0 11.1 11.3": ["redtube"], "-3.2 8.8 1.5": ["opportuntiy"], "13.4 0.2 2.7": ["emuse"], "10.5 -3.6 6.6": ["booksignings"], "3.7 3.6 -6.9": ["whoe"], "0.3 -2.1 5.8": ["explaning"], "4.4 9.8 6.2": ["sluttier"], "-2.4 7.4 4.9": ["mercaptans"], "2.7 2.7 10.9": ["moderations"], "6.9 8.5 6.7": ["fissioning"], "16.1 8.5 13.2": ["louvred"], "10.6 3.0 17.3": ["sulfolane"], "6.7 15.4 3.1": ["therby"], "21.4 18.8 38.9": ["sandworm"], "4.4 4.0 14.3": ["mdb"], "8.3 18.7 14.4": ["seaquake"], "8.8 20.3 23.2": ["eys"], "-2.3 14.6 -9.0": ["revulsed"], "-0.1 10.2 12.3": ["achi"], "17.6 19.9 30.0": ["bullrushes"], "7.5 17.9 10.5": ["terr"], "17.0 1.8 25.8": ["titch"], "16.1 1.6 37.2": ["bibbed"], "-3.1 12.2 5.9": ["hijrah"], "14.3 3.8 9.7": ["centrum"], "9.1 -1.8 28.1": ["milkfat"], "-0.7 4.8 6.4": ["levocetirizine"], "12.3 2.7 11.6": ["colleting"], "-1.0 -0.3 11.3": ["threehour"], "9.2 7.2 21.6": ["klub"], "11.2 29.6 19.2": ["slavemasters"], "4.3 7.1 10.1": ["tractions"], "7.6 21.1 11.9": ["ratiocination"], "13.8 11.3 13.3": ["noninteractive"], "11.7 14.6 -8.1": ["turbojets"], "6.9 23.6 -5.4": ["uncontroversially"], "20.5 13.9 39.6": ["diporeia"], "-10.9 5.5 -0.7": ["iclicker"], "12.9 0.6 6.1": ["vidcast"], "9.4 3.8 9.8": ["fabu"], "2.0 6.8 8.5": ["hassel"], "-0.7 -3.1 2.4": ["shools"], "15.1 4.4 8.7": ["semicarbazide"], "9.5 17.7 12.4": ["wilfing"], "3.4 13.5 8.5": ["wicca"], "-3.3 7.4 9.8": ["taekwon"], "-1.6 6.6 6.7": ["illumigene"], "21.7 7.9 24.5": ["binturong"], "1.2 6.8 12.9": ["vivir"], "6.1 3.6 7.2": ["neurophysiologic"], "-3.6 24.5 8.8": ["noncombative"], "7.0 3.2 5.9": ["communi"], "6.9 10.4 14.6": ["lateralized"], "4.7 4.9 -2.9": ["trainning"], "10.4 3.2 24.2": ["swiming"], "5.5 7.6 8.4": ["sustainablity"], "9.0 12.5 -2.7": ["surreptiously"], "9.1 4.0 33.3": ["forequarter"], "23.6 4.0 6.3": ["telecomunications"], "20.0 -1.8 12.6": ["malternative"], "14.5 -3.9 15.2": ["unbonded"], "9.9 6.9 16.4": ["homburg"], "11.3 13.2 13.5": ["hermano"], "4.0 13.5 16.1": ["unflagged"], "-7.2 7.5 0.7": ["overdrawal"], "-0.0 18.0 6.7": ["tribalised"], "13.9 15.4 30.9": ["sulphurs"], "1.8 2.6 9.2": ["comitology"], "9.3 7.2 8.0": ["biophotonic"], "-3.4 3.1 7.8": ["patil"], "5.9 3.4 12.3": ["bowlfest"], "2.4 14.3 1.9": ["walcott"], "2.1 3.6 8.2": ["almsot"], "0.5 14.6 -5.8": ["rolein"], "15.1 7.8 17.7": ["pocketfuls"], "0.1 6.0 2.5": ["pretests"], "-4.3 4.7 19.0": ["preharvest"], "18.2 10.7 26.7": ["chrysalides"], "10.7 4.6 58.0": ["greenling"], "-0.4 18.2 2.8": ["comunication"], "7.2 2.1 4.5": ["aseries"], "4.1 6.0 11.8": ["oenologists"], "-8.7 3.6 6.2": ["datarate"], "20.6 18.6 10.1": ["trillionaires"], "10.0 0.4 12.3": ["twinsets"], "-0.7 15.3 19.2": ["helitack"], "-3.4 9.3 5.2": ["nonequilibrium"], "6.1 14.1 5.8": ["popularist"], "3.7 2.1 12.1": ["hernandez"], "-2.1 13.9 6.7": ["publick"], "7.6 10.7 25.9": ["dollied"], "1.1 3.6 3.7": ["immeidately"], "0.0 4.3 6.1": ["membes", "benzimidazole"], "2.2 13.9 14.6": ["motha"], "5.8 1.5 17.3": ["stepdancing"], "2.1 11.9 4.5": ["coverline"], "6.0 15.9 -0.1": ["acutest"], "-4.0 18.8 10.9": ["queston"], "0.8 -2.8 -0.5": ["toparticipate"], "8.6 15.2 3.6": ["secretely"], "1.5 12.5 -4.0": ["unencrypt"], "15.2 10.5 9.8": ["deconstructivist"], "10.1 13.6 21.9": ["toddies"], "8.7 14.6 16.0": ["tarsal"], "-3.0 12.3 -0.6": ["firstdegree"], "3.4 13.9 10.4": ["kipah"], "5.9 11.6 2.4": ["parrallel"], "9.4 17.4 25.3": ["accidentaly"], "11.8 8.3 2.5": ["sorrounding"], "-0.8 20.0 16.4": ["adulticiding"], "-2.1 9.8 10.4": ["incardinated"], "11.2 16.4 9.4": ["ulcerous"], "9.1 15.0 12.8": ["flabbergast"], "2.7 8.7 0.8": ["outsung"], "-1.7 5.1 2.3": ["vires"], "8.7 14.1 5.7": ["lilywhite"], "2.5 24.1 7.8": ["arguers"], "6.2 -0.9 4.3": ["spor"], "5.0 8.2 12.2": ["reinfused"], "13.5 1.8 0.5": ["themain"], "-1.4 14.7 10.5": ["orderto"], "-1.5 9.8 6.2": ["outqualify"], "10.6 18.4 11.0": ["mommie"], "2.1 -0.1 4.2": ["looksoftware"], "3.6 1.9 13.2": ["matthews"], "15.5 2.8 7.7": ["disgorgements"], "17.2 3.8 7.7": ["demutualisations"], "5.1 -1.2 5.6": ["ingle"], "8.7 6.6 4.1": ["videographic"], "0.3 3.3 11.9": ["comminuted"], "0.2 -2.1 -1.2": ["outrighting"], "9.3 6.2 24.4": ["cruisey"], "18.2 10.3 24.9": ["nonvenomous"], "14.7 10.1 3.7": ["blackberrys"], "17.5 12.1 8.8": ["unfathomed"], "-0.8 13.3 18.8": ["eradications"], "4.2 9.4 7.9": ["nucleosynthesis"], "4.2 7.0 5.3": ["sericitic"], "-6.7 11.6 0.8": ["hassan"], "6.1 6.5 2.7": ["cameoed"], "14.5 4.9 26.3": ["burfi"], "-0.6 7.3 19.5": ["topfen"], "3.6 12.5 3.6": ["defibrilator"], "-7.0 5.5 3.1": ["catecheses"], "-0.3 3.3 -1.2": ["statt"], "6.0 9.4 16.4": ["miguel"], "6.5 1.7 -0.1": ["cto"], "1.9 6.4 7.4": ["flumazenil"], "9.6 6.4 0.3": ["talkshop"], "-7.2 -9.3 -2.8": ["neurorehabilitation"], "2.6 -1.3 12.4": ["bioadhesive"], "17.3 8.6 14.1": ["sns"], "-7.6 5.7 5.4": ["pinchrunner"], "5.7 8.3 3.9": ["seguing"], "-1.7 7.7 4.6": ["uac"], "5.6 0.7 7.6": ["rapide"], "7.3 14.5 1.6": ["sensoring"], "7.8 9.1 11.3": ["carsickness"], "-2.4 -2.0 8.1": ["accel"], "-3.3 2.4 11.6": ["nickvoices"], "5.7 17.7 25.1": ["chubbing"], "16.7 8.0 31.6": ["storebought"], "4.5 18.3 1.6": ["idolisation"], "10.7 6.3 15.8": ["shola"], "0.5 10.4 13.5": ["dephosphorylation"], "6.3 6.2 16.3": ["aar"], "10.9 11.4 17.0": ["waitng"], "12.8 -1.2 29.3": ["stovies"], "0.8 4.5 3.6": ["cambios"], "-0.1 9.1 7.1": ["descriptiveness"], "10.1 12.3 12.8": ["deorbited", "hester"], "14.2 10.4 22.9": ["pila"], "-5.6 -0.4 2.0": ["clotrimazole"], "10.8 17.0 -0.5": ["blazar"], "4.0 11.5 3.1": ["dogeared"], "16.7 11.9 7.3": ["clomps"], "15.6 16.9 4.2": ["ignominous"], "13.4 2.6 12.9": ["postrecession"], "15.6 9.4 3.6": ["filetypes"], "8.9 5.0 1.3": ["nght"], "11.5 11.5 19.0": ["pongs"], "-0.4 -5.5 3.9": ["cpd"], "0.5 5.1 9.4": ["songlike"], "3.3 -0.3 13.0": ["pito"], "21.5 15.2 29.2": ["hummock"], "8.2 2.5 17.7": ["frie"], "13.0 20.8 12.8": ["greeneries"], "9.5 -0.8 7.2": ["estan"], "4.4 0.8 20.3": ["aral"], "1.8 7.3 20.6": ["huan"], "-2.1 4.0 6.2": ["untaped"], "7.5 12.7 4.6": ["cardinally"], "12.6 7.1 40.1": ["aquiculture"], "4.5 6.5 -3.4": ["alledging"], "7.8 10.8 9.1": ["ifthey"], "3.1 -4.0 -0.5": ["saysthe"], "8.6 14.8 5.2": ["amzing"], "1.2 0.3 9.7": ["methaqualone"], "4.7 10.9 5.8": ["kramer"], "15.4 3.7 25.2": ["mangabey"], "0.3 3.9 5.7": ["coch"], "6.2 8.3 2.8": ["respose"], "4.9 8.6 2.8": ["aphasic"], "3.8 8.5 9.6": ["themoment"], "22.2 21.1 30.1": ["ogress"], "5.3 17.4 2.0": ["priviliges"], "2.8 -0.3 0.8": ["valtorcitabine"], "13.0 8.1 11.1": ["enegy"], "5.1 8.4 5.7": ["photoconductive"], "7.8 11.1 12.2": ["gridlocking"], "5.2 1.0 2.9": ["stro"], "-8.6 0.9 5.0": ["combinability"], "18.0 -4.5 7.1": ["polyster"], "17.2 7.0 28.4": ["suger"], "8.6 9.4 13.8": ["welcomers"], "12.9 16.6 2.5": ["closeting"], "-2.4 -0.3 5.8": ["urinalyses"], "18.5 -10.0 5.5": ["halfyear"], "-1.9 4.2 8.9": ["multicap"], "11.7 13.4 8.1": ["weaking"], "3.1 18.6 16.2": ["coaling"], "5.3 -4.9 12.0": ["eraill"], "11.1 18.3 2.0": ["antithetic"], "1.4 7.6 7.0": ["unaswered"], "3.6 14.4 6.3": ["microkernels"], "15.4 12.9 13.4": ["miserabilist"], "16.3 16.2 9.0": ["zaibatsu"], "20.3 16.9 8.3": ["screecher"], "1.3 9.9 6.8": ["odio"], "2.7 5.9 21.7": ["constitutionals"], "9.3 8.4 14.6": ["wholefoods"], "3.2 16.3 4.2": ["undersecretariat"], "10.7 9.1 8.1": ["gleamingly"], "8.7 23.3 6.9": ["wussed"], "3.9 16.5 16.2": ["pellicle"], "17.0 18.6 12.9": ["assclown"], "14.6 -1.4 10.5": ["divident"], "15.7 13.4 30.0": ["fishwives"], "8.5 15.0 21.6": ["genever"], "3.2 7.3 21.0": ["idi"], "9.6 11.6 7.4": ["octogenerian"], "-1.5 11.9 4.2": ["outdance"], "3.4 13.3 16.2": ["sarcoid"], "9.2 7.3 10.1": ["baaa"], "-3.4 1.6 -1.4": ["allstate"], "14.5 32.5 15.2": ["asura"], "0.7 11.4 22.1": ["layday"], "19.2 8.3 13.8": ["dorkier"], "11.4 11.7 13.6": ["fingerpicked"], "6.5 -3.3 14.8": ["rsp"], "1.5 6.9 7.7": ["pruritic"], "5.6 15.8 15.3": ["grippe"], "-3.2 4.1 4.7": ["bankfull"], "8.2 10.8 15.9": ["haemagglutinin"], "10.2 12.3 15.4": ["hecka"], "7.2 9.2 23.6": ["bulkheading"], "9.1 13.3 10.3": ["snarkiest"], "6.9 12.1 17.0": ["gumi"], "0.7 10.4 15.6": ["jegging"], "15.5 5.7 13.2": ["menders"], "16.4 30.2 19.7": ["tauren"], "-2.9 3.3 15.2": ["teresa"], "6.4 24.2 15.0": ["cocksuckers"], "-8.5 -1.1 -1.0": ["evals"], "-0.7 17.4 3.3": ["nonpolitician"], "-1.5 15.8 9.3": ["hussain"], "15.4 29.2 12.4": ["establishmentarians"], "-0.9 15.4 9.8": ["ballteam"], "3.2 -3.3 10.1": ["baw"], "14.0 21.8 19.3": ["spanker"], "9.5 9.9 20.9": ["benzoin"], "6.9 3.4 -10.4": ["wwas"], "3.0 10.4 9.0": ["puedo"], "6.5 7.3 10.4": ["reli"], "6.5 25.5 8.2": ["recces"], "4.1 10.3 6.9": ["diplexer"], "7.3 17.6 5.3": ["mouthings"], "0.5 11.5 11.6": ["grandchilden"], "24.9 20.0 15.7": ["gewgaw"], "-8.9 33.7 -0.4": ["milblogs"], "10.4 3.2 9.8": ["iplayer"], "9.8 -0.4 32.5": ["spiedies"], "4.3 9.4 6.4": ["nikon", "tigerblood"], "9.3 5.0 9.7": ["dumbek"], "21.7 1.8 11.2": ["megamalls"], "13.2 14.8 25.4": ["antarctica"], "5.6 22.4 3.4": ["phreaking"], "10.1 18.6 10.6": ["wiseman"], "13.2 2.1 14.1": ["abhishekam"], "17.1 13.6 18.1": ["clublike"], "15.2 11.6 20.3": ["freakily"], "-6.3 -0.9 15.0": ["mandies"], "13.7 2.2 1.7": ["covermount"], "-6.6 -0.8 7.0": ["chiro"], "11.5 9.3 20.4": ["toastiness"], "6.1 0.2 9.9": ["mercato"], "7.2 8.0 19.5": ["jayenge"], "2.7 7.7 3.3": ["pilocarpine"], "4.2 9.9 4.1": ["terminuses"], "1.4 11.6 7.6": ["fourthand"], "5.8 14.3 -5.3": ["miscalled"], "11.8 10.7 28.6": ["aumakua"], "25.4 12.1 21.6": ["gnomon"], "0.1 9.5 -7.9": ["relese"], "-0.2 -0.2 6.1": ["litt"], "18.8 24.1 11.5": ["satrapies"], "4.6 15.7 16.9": ["ponting"], "16.7 23.2 10.8": ["unblurred"], "-3.9 7.4 -3.4": ["mez"], "22.6 3.3 22.3": ["volute"], "0.5 -4.6 11.2": ["oherwydd"], "5.5 -3.5 -3.3": ["focuson"], "7.1 -3.8 1.2": ["appoved"], "5.6 12.7 6.6": ["muliple"], "-2.6 13.6 9.1": ["ethosuximide"], "11.3 10.8 13.8": ["skidplate"], "8.5 12.4 17.3": ["polyhedra"], "5.9 5.8 -3.0": ["businees"], "3.3 -5.5 3.6": ["thinkpad"], "11.9 5.3 12.0": ["shimmed"], "8.7 12.9 11.4": ["cyberlockers"], "19.4 14.5 9.7": ["suiter"], "0.9 -1.4 5.3": ["vasa"], "5.4 6.6 15.7": ["isla"], "-2.7 -1.5 6.8": ["encephalocele"], "3.0 3.7 6.6": ["dancemakers"], "2.2 2.0 18.3": ["milton"], "4.6 11.3 14.9": ["zucchetto"], "0.5 4.0 7.9": ["arriver"], "10.1 29.4 4.7": ["proconsuls"], "8.7 5.8 31.3": ["flavorfully"], "8.2 3.2 11.3": ["geochronology"], "12.5 15.1 7.8": ["superteams"], "2.2 8.4 14.9": ["summerhouses"], "-2.2 5.8 -0.4": ["repolarization"], "3.3 5.4 6.7": ["carboxylate"], "5.5 19.3 9.6": ["demagogical"], "3.7 15.0 17.7": ["pollarding"], "7.4 9.7 17.1": ["suezmaxes"], "7.7 7.8 10.3": ["strlen"], "6.2 23.3 12.9": ["reverenced"], "12.8 19.3 35.4": ["northeasters"], "0.3 2.0 18.4": ["halla"], "1.7 4.5 22.3": ["xian"], "-0.0 3.1 -0.0": ["ftc"], "8.9 4.3 9.4": ["setar"], "22.1 12.2 25.3": ["tangly"], "4.3 -5.1 3.4": ["jeunes"], "11.1 12.4 6.3": ["hava"], "-2.3 10.1 5.2": ["teledramas"], "2.3 5.5 7.3": ["panchyats"], "-1.4 4.3 3.7": ["microscopist"], "-1.2 12.2 7.7": ["shishya"], "10.3 14.0 6.4": ["relocked"], "-6.5 8.1 1.2": ["toachieve"], "7.7 7.9 -1.5": ["aql"], "17.1 4.0 7.9": ["mobivention"], "4.7 -0.8 6.0": ["adsorbs"], "-0.5 6.0 8.2": ["tollywood"], "6.2 12.3 4.1": ["cacher"], "16.8 0.4 28.4": ["kete"], "3.2 22.0 10.8": ["tendentiousness"], "-0.2 16.7 13.5": ["anthelmintics"], "-2.4 -4.3 13.1": ["flunixin"], "3.0 4.1 -2.8": ["electrostimulation"], "-0.8 3.8 2.2": ["comitment"], "10.4 18.6 19.5": ["poot"], "0.0 12.2 16.1": ["roseola"], "10.7 14.2 5.2": ["superdad"], "8.5 10.5 4.1": ["geoinformation"], "18.0 4.0 12.2": ["coronets"], "-3.7 14.3 3.9": ["deductors"], "4.4 13.0 27.1": ["smartweed"], "8.4 15.0 0.9": ["underappreciate"], "20.9 14.7 21.4": ["beermaking"], "2.4 5.1 8.0": ["souvent"], "1.2 0.7 13.1": ["bateyes"], "2.8 -0.1 12.0": ["dels"], "6.0 5.4 32.5": ["salvers"], "9.3 9.2 6.8": ["naughts"], "13.6 7.6 26.7": ["midrib"], "5.4 3.8 2.9": ["envi"], "3.2 1.5 6.9": ["underbidders"], "8.1 14.6 18.6": ["monophyletic"], "17.1 9.3 15.2": ["nintendogs"], "16.2 5.7 29.1": ["krumkake"], "4.7 9.3 38.7": ["uplake"], "1.4 17.6 22.4": ["undammed"], "2.9 14.0 10.4": ["humourists"], "21.6 23.2 31.8": ["mermen"], "-2.3 17.6 10.8": ["reluctancy"], "12.4 -4.8 34.7": ["ogo"], "0.5 0.7 17.2": ["rch"], "6.5 4.0 23.9": ["woodlark"], "5.6 5.7 14.7": ["formful"], "3.4 2.3 11.7": ["durries"], "10.1 18.2 12.0": ["larf"], "3.1 0.4 12.2": ["wollastonite"], "19.9 3.9 31.9": ["tamarinds"], "6.8 13.0 9.4": ["quartertime"], "10.9 7.3 3.2": ["spatting"], "12.9 15.0 12.6": ["weirding"], "10.3 26.3 11.4": ["dopiness"], "16.2 8.4 11.9": ["bondo"], "2.2 19.7 15.9": ["nade"], "6.0 -1.6 6.0": ["pipeliners"], "4.1 1.1 6.3": ["linecards"], "6.2 1.5 14.5": ["workscope"], "4.3 12.3 15.8": ["hima"], "4.2 16.8 10.0": ["overmanage"], "7.9 2.4 13.0": ["iro"], "4.0 8.4 4.1": ["headcams"], "14.6 17.0 11.6": ["unlimitedly"], "4.5 -5.7 2.6": ["srp"], "18.3 -2.4 8.2": ["industria"], "11.5 -1.4 11.3": ["onan"], "6.1 0.3 11.4": ["yma"], "6.7 15.7 8.4": ["ursula"], "6.9 4.4 6.1": ["symphonist"], "-0.2 31.3 7.3": ["factionalist"], "-0.6 7.8 21.8": ["antiquers"], "8.2 9.8 11.8": ["ringbearers"], "-14.9 3.0 -3.1": ["insp"], "15.8 10.1 28.5": ["genoise"], "16.3 1.1 8.7": ["plas"], "-1.0 17.9 13.5": ["stressfully"], "7.3 6.6 25.2": ["oku"], "9.8 15.6 13.3": ["ooky"], "3.9 12.0 7.0": ["deglamourised"], "5.3 18.3 7.7": ["teargassing"], "7.0 -1.7 9.3": ["tinsmiths"], "8.4 5.3 6.7": ["virusworthy"], "5.9 7.5 5.4": ["flexures"], "11.8 4.6 14.7": ["spinels"], "6.1 18.3 10.5": ["oxacillin"], "20.0 9.5 18.3": ["eyebolt"], "-2.3 0.9 9.3": ["gregory"], "2.6 0.6 3.1": ["expecte"], "3.8 4.3 8.7": ["overallocation"], "8.4 6.5 19.2": ["plov"], "-1.0 5.5 7.7": ["trippings"], "6.4 18.8 21.1": ["striga"], "12.3 25.6 21.5": ["jabroni"], "3.5 2.8 11.7": ["artistas"], "5.9 6.3 39.4": ["virginica"], "6.9 13.2 11.8": ["yal"], "16.3 4.0 16.5": ["leathercraft"], "0.2 14.3 10.5": ["quallies"], "10.6 28.9 9.3": ["mulitplayer"], "9.3 10.9 12.7": ["steaminess"], "2.7 26.7 4.5": ["swiftboated"], "3.2 14.1 9.1": ["overcriminalization"], "8.1 5.6 3.0": ["emmisions"], "6.7 -0.3 -0.8": ["interna"], "0.4 4.2 5.8": ["leachability"], "12.0 20.9 19.2": ["kukri"], "14.8 18.2 21.6": ["hoves"], "6.6 11.7 14.1": ["gavin"], "4.6 -1.1 -3.3": ["helds"], "2.2 5.8 4.5": ["brochureware"], "9.8 21.7 13.6": ["inattentively"], "15.5 11.0 18.0": ["berzerkeley"], "5.8 6.4 12.2": ["polyketides"], "7.2 36.7 11.4": ["terroists"], "14.6 12.4 12.0": ["hostie"], "0.3 1.6 -2.1": ["feeamanellaah"], "6.3 5.0 11.2": ["ranty"], "14.9 -0.6 11.6": ["lilted"], "11.5 15.1 20.8": ["maynard"], "3.3 12.8 20.1": ["ingrediants"], "4.6 20.8 26.5": ["maror"], "14.2 -0.0 4.8": ["fueld"], "6.5 21.4 12.2": ["inarticulacy"], "15.7 10.7 23.4": ["fertilises"], "7.5 10.6 26.3": ["loganberries"], "16.0 12.3 1.9": ["eldorado"], "13.0 24.8 10.5": ["chatterer"], "0.5 1.3 16.8": ["loppet"], "14.2 21.5 11.1": ["rocketeer"], "9.4 2.2 8.6": ["reupholstery"], "7.6 15.5 7.3": ["awws"], "7.3 11.3 8.4": ["pluralized"], "12.4 9.5 3.4": ["analyts"], "5.1 4.3 5.8": ["keyfobs"], "27.3 19.6 24.3": ["paramecium"], "-2.8 7.2 -0.6": ["allthough"], "0.5 16.1 0.8": ["ibra"], "-0.9 9.2 22.8": ["tupping"], "9.7 2.0 33.8": ["maile"], "16.0 6.0 16.2": ["titin"], "10.6 0.2 9.8": ["redisplay"], "3.6 -3.7 -4.9": ["expeted"], "7.8 0.8 5.5": ["equipe"], "-3.3 2.3 -3.8": ["fluphenazine"], "6.5 19.8 5.5": ["anomic"], "16.2 8.8 9.3": ["volkswagen"], "-1.3 4.5 12.8": ["givings"], "6.8 10.1 9.7": ["rahsheen"], "12.0 3.0 9.9": ["equiment"], "10.9 3.1 19.3": ["stockdraw"], "0.0 4.3 9.2": ["farletuzumab"], "0.8 6.8 4.3": ["decommitments"], "4.7 7.3 13.8": ["bushwalks"], "1.0 3.6 15.3": ["baju"], "8.2 8.8 23.7": ["fancified"], "13.0 1.1 12.1": ["thermoformers"], "5.6 6.7 8.4": ["amish"], "0.2 9.5 14.7": ["hyeong"], "1.2 -0.0 11.1": ["ared"], "5.3 6.8 11.5": ["quienes"], "9.3 16.1 9.5": ["miscommunicate"], "15.3 16.4 10.9": ["embarrassedly"], "14.3 10.6 23.5": ["ixora"], "4.2 19.3 0.3": ["tream"], "20.3 14.4 21.3": ["faddishness"], "7.1 6.2 18.9": ["legbreaks"], "13.8 -3.3 17.6": ["waxers"], "12.0 10.8 5.5": ["trickily"], "16.2 8.2 24.7": ["quaysides"], "14.2 7.5 17.2": ["brickmaking"], "22.0 18.0 28.9": ["backcast"], "18.5 4.1 16.4": ["fannie"], "5.6 14.6 16.0": ["hings"], "1.6 18.3 13.3": ["filovirus"], "11.5 -3.0 1.4": ["ejournal"], "7.8 -3.9 3.1": ["owa"], "4.9 7.0 23.9": ["shallowing"], "2.0 -4.7 0.4": ["neez"], "5.6 6.5 23.9": ["cheesemongers"], "13.9 8.1 27.1": ["floppiness"], "11.7 -5.5 0.8": ["electrotechnology"], "1.1 20.4 20.6": ["swiftboats"], "1.3 3.6 2.8": ["peformer"], "8.5 25.2 9.9": ["lewrockwell"], "14.8 3.2 25.1": ["culturists"], "16.8 -0.7 14.4": ["gian"], "9.8 7.9 14.3": ["alexandrite"], "-0.5 9.2 13.2": ["patrolwoman"], "8.3 2.5 6.1": ["mde"], "16.8 47.2 6.1": ["counterassault"], "1.5 28.4 9.9": ["monotheisms"], "12.2 2.3 19.8": ["housedresses"], "13.1 21.4 -1.6": ["proselytisers"], "10.1 9.2 28.7": ["pitchin"], "8.7 14.2 0.3": ["rabab"], "10.2 12.7 8.5": ["bauls"], "5.2 -1.2 19.8": ["fertilizations"], "4.9 10.6 7.3": ["toothing"], "10.6 17.3 14.8": ["mundaneness"], "17.7 18.3 8.1": ["pubicly"], "9.9 8.6 7.6": ["hadron"], "13.6 0.7 26.5": ["mangetout"], "13.5 7.1 -4.4": ["sportlifestyle"], "-13.3 3.1 -11.2": ["mantained"], "-3.6 3.3 9.5": ["plication"], "7.6 6.7 6.3": ["anlaysts"], "2.3 8.6 3.8": ["newswriter"], "4.0 11.7 5.9": ["overstaff"], "8.8 6.7 18.6": ["pobre"], "7.0 7.8 6.1": ["catridges"], "17.9 9.9 49.6": ["mackeral"], "5.0 16.4 4.9": ["philosophised"], "2.3 8.3 7.0": ["apitherapy"], "7.9 17.8 10.5": ["trafficing"], "11.8 13.1 19.7": ["lobos"], "16.2 10.1 25.0": ["sterno"], "3.1 5.1 -0.2": ["erhalten"], "11.9 -9.5 9.3": ["millionto"], "6.6 3.4 6.3": ["majorleague"], "-0.9 16.4 -2.7": ["railmen"], "20.9 16.0 31.1": ["saxifrage"], "3.3 17.9 7.2": ["hawan"], "12.9 9.2 9.4": ["keyboarded"], "18.4 8.1 19.8": ["palustris"], "5.3 17.1 11.7": ["beauracracy"], "18.2 0.1 17.8": ["strummin"], "6.7 9.4 6.1": ["neuer"], "9.4 20.9 2.0": ["adulating"], "-0.2 9.7 13.5": ["tumhe"], "5.9 -5.0 7.6": ["exlusively"], "13.4 6.8 12.5": ["queensland"], "-0.6 -2.1 7.7": ["cholestyramine"], "5.1 10.0 23.4": ["dhokla"], "4.6 10.9 5.2": ["benefactions"], "11.9 2.4 1.9": ["whiled"], "-2.9 -6.3 15.6": ["biosamples"], "2.0 5.4 6.4": ["refluxing"], "-3.9 -4.4 1.1": ["rene"], "15.1 7.2 9.9": ["wizz"], "11.1 8.5 9.4": ["tienda"], "12.7 7.8 3.8": ["dodginess"], "3.1 5.6 3.5": ["draftsperson"], "5.3 27.9 -1.0": ["safehavens"], "12.3 4.1 9.0": ["xenoestrogens"], "-2.3 2.3 1.5": ["munajat"], "15.5 20.8 14.3": ["overarm"], "-5.6 4.9 9.9": ["tweakings"], "5.6 15.5 12.2": ["superzooms"], "3.3 1.3 20.1": ["golas"], "7.3 5.5 -1.6": ["ahmedabad"], "2.6 7.7 6.2": ["inworld"], "-0.0 7.2 20.2": ["tali"], "18.2 21.4 17.1": ["darkling"], "5.7 4.1 8.0": ["orangeries"], "1.6 20.4 9.6": ["chkdsk"], "9.4 3.0 33.5": ["puti"], "6.2 12.1 1.1": ["cyle"], "10.6 4.3 8.0": ["northend"], "6.4 24.5 10.1": ["alaykum"], "-0.0 3.8 12.3": ["reimplant"], "-9.5 3.7 4.6": ["sene"], "5.0 0.2 10.3": ["nadaswaram"], "-1.6 11.1 12.2": ["chemisty"], "8.6 22.4 5.2": ["superheroism"], "4.1 8.7 17.2": ["manured"], "11.0 -2.2 8.9": ["bips"], "20.7 4.6 7.3": ["turnstyles"], "3.8 5.8 17.2": ["cound"], "0.2 8.6 7.6": ["benefical"], "11.3 13.3 16.2": ["ebru"], "3.1 1.3 2.6": ["aned"], "-1.9 14.8 5.6": ["complementarily"], "0.2 13.9 8.0": ["creats"], "13.5 0.7 4.3": ["arange"], "2.6 11.4 22.6": ["dioecious"], "4.1 1.5 10.1": ["homeopathics"], "13.8 12.7 -2.1": ["esentially"], "16.3 5.8 9.3": ["motherese"], "14.7 7.3 3.0": ["taxpapers"], "2.1 -0.1 1.8": ["doivent"], "11.2 -5.4 20.3": ["polk"], "14.1 20.7 7.2": ["demolishers"], "-0.9 18.0 1.6": ["flightcrew"], "4.1 -1.7 10.2": ["crosstie"], "9.7 9.4 11.6": ["equitize"], "17.7 12.6 24.4": ["fendering"], "8.4 17.4 7.2": ["ramshackled"], "-2.7 7.2 12.4": ["ility"], "10.5 3.9 8.2": ["tippee"], "10.2 0.5 4.7": ["roku"], "1.4 15.5 12.3": ["downselect"], "5.6 18.2 13.6": ["ifyou"], "4.1 15.3 6.5": ["favoriting"], "2.9 14.0 4.8": ["ayers"], "13.0 6.6 3.2": ["imprinter"], "9.1 5.7 18.7": ["grindhouses"], "8.7 1.1 -0.0": ["counci"], "19.2 5.2 15.7": ["inche"], "1.5 20.2 0.9": ["credability"], "16.3 8.7 21.1": ["boomin"], "3.3 5.3 18.1": ["tatou"], "12.1 2.1 6.1": ["desgined"], "13.4 12.6 11.8": ["bunkbed"], "2.9 14.4 6.1": ["paticular"], "1.2 16.6 -7.4": ["cdv"], "5.7 6.0 9.1": ["fluidized"], "5.8 11.1 14.5": ["bullae"], "3.8 -0.7 4.8": ["alfuzosin"], "0.6 3.9 4.0": ["valeted"], "18.7 17.0 27.5": ["bushbuck"], "11.6 6.0 36.7": ["tamarillo"], "6.7 10.6 44.1": ["steelie"], "2.9 11.8 9.6": ["genomically"], "10.9 -2.8 6.2": ["rete"], "6.7 10.3 23.1": ["dought"], "5.2 15.3 15.7": ["sieverts"], "17.2 15.8 23.4": ["tempters"], "8.1 22.4 11.3": ["monologuing"], "7.7 13.6 12.1": ["priggishness"], "25.7 7.0 29.6": ["hempseed"], "7.4 2.5 18.9": ["skateway"], "5.7 20.2 7.7": ["unskillful"], "-0.4 -1.3 5.8": ["kmt"], "5.6 10.8 8.0": ["iterators"], "0.9 -2.0 4.3": ["thsd"], "10.0 9.2 15.3": ["progressivevoicedaily"], "4.3 1.6 3.0": ["rekeyed"], "19.1 1.7 2.6": ["readerboard"], "13.0 10.5 6.3": ["blooks"], "6.1 7.3 8.0": ["musik"], "23.0 9.4 22.0": ["oblongs"], "6.3 14.1 18.6": ["woodstock"], "3.2 7.7 5.0": ["symphonically"], "4.4 21.0 2.1": ["promptitude"], "-0.9 9.4 16.2": ["filaggrin"], "4.4 -2.0 3.2": ["habitational"], "5.5 9.1 16.7": ["paisano"], "-5.4 4.8 7.3": ["hypopnea"], "2.1 7.7 20.4": ["sada"], "17.5 3.5 19.6": ["cantilevering"], "5.1 9.7 3.5": ["contendors"], "-3.4 2.7 21.0": ["quinta"], "9.3 11.4 20.6": ["polars"], "11.1 0.8 24.8": ["miki"], "2.8 2.8 -5.9": ["upport"], "4.8 9.5 5.2": ["rdf"], "2.8 11.1 15.8": ["tempertures"], "11.1 19.0 14.5": ["ultima"], "10.5 11.2 4.5": ["polarimetry"], "0.1 15.4 14.3": ["kotong"], "21.8 -2.4 9.6": ["nontech"], "9.5 19.8 1.8": ["captious"], "22.0 13.0 5.5": ["counterbidders"], "10.0 23.7 15.1": ["yeehaw"], "6.7 21.6 18.5": ["suhur"], "3.9 -0.7 14.4": ["doux"], "2.2 4.3 14.8": ["pakhawaj"], "6.9 1.2 2.8": ["cashcard"], "12.1 19.0 32.1": ["mushi"], "-3.8 11.9 -4.3": ["comman"], "4.0 14.4 1.7": ["strikethrough"], "9.9 22.1 4.0": ["pharisees"], "11.8 5.1 2.9": ["andothers"], "14.1 14.2 20.3": ["exclosures"], "0.7 1.9 2.7": ["steped"], "11.0 7.7 3.5": ["orchestrion"], "2.3 33.0 9.1": ["rankism"], "-1.0 3.2 -0.5": ["produciton"], "24.5 19.2 22.0": ["matchwood"], "1.9 0.2 6.9": ["detemine"], "20.0 20.5 21.8": ["releasers"], "25.0 16.6 22.4": ["beefeaters"], "19.2 9.7 10.7": ["hundres"], "13.1 9.4 11.1": ["kabosh"], "-0.4 1.5 11.3": ["linoleic"], "10.6 6.8 19.5": ["cardy"], "4.4 4.0 8.2": ["evironmental"], "9.8 9.1 1.3": ["palmprint"], "2.5 3.3 2.7": ["forfiet"], "4.2 17.5 12.3": ["perserverence"], "13.1 17.0 8.6": ["sacrilegiously"], "2.1 46.0 4.4": ["munafiqs"], "12.7 8.8 12.0": ["eeh"], "16.2 9.1 4.1": ["stinkbomb"], "9.8 21.2 23.3": ["indulgers"], "12.3 -1.0 11.8": ["ayem"], "1.2 16.8 12.0": ["thoughtout"], "3.8 0.7 6.0": ["emusic"], "4.7 21.6 7.4": ["anamoly"], "-0.9 9.4 10.4": ["discribed"], "4.8 2.1 2.0": ["businessand"], "3.4 14.1 3.3": ["actualizes"], "0.3 20.6 11.1": ["introspections"], "8.0 11.9 4.5": ["unsere"], "7.0 16.4 -1.0": ["arrestors"], "5.1 -8.8 5.1": ["prelicensing"], "-3.0 16.6 6.6": ["conversos"], "-7.9 15.7 3.1": ["decsions"], "-7.6 13.1 14.6": ["zainichi"], "11.9 11.7 21.9": ["bialy"], "0.8 3.4 8.2": ["diphosphate"], "11.7 11.3 11.6": ["midstaters"], "19.7 18.3 43.6": ["sealions"], "5.5 5.1 10.7": ["bicuspid"], "9.5 18.1 8.2": ["mirthfully"], "15.6 5.6 23.2": ["truc"], "2.6 22.1 0.8": ["nonbelieving"], "-2.4 17.7 0.5": ["maximalists"], "5.4 2.2 12.8": ["thel"], "6.0 10.5 27.9": ["powerboaters"], "9.5 -1.5 1.5": ["wonkier"], "19.8 20.3 15.7": ["unmoveable"], "6.9 13.9 6.4": ["apk"], "12.0 10.7 15.4": ["geno"], "1.1 0.1 2.0": ["implentation"], "14.4 11.1 39.7": ["auks"], "8.0 1.0 39.7": ["tagliolini"], "6.0 21.1 4.1": ["underplanned"], "9.9 5.7 8.7": ["routeing"], "7.4 11.3 4.8": ["weening"], "14.1 0.6 14.8": ["rhinestoned"], "9.1 17.5 1.6": ["reenergise"], "7.0 10.3 7.0": ["sice"], "13.0 -0.3 31.5": ["milanesa"], "-8.8 9.1 6.8": ["damsire"], "0.4 9.2 15.6": ["tempus"], "6.6 1.9 4.2": ["prepackage"], "0.4 -2.8 -5.6": ["lookforward"], "12.5 20.1 13.0": ["psephological"], "11.8 5.0 -4.3": ["devloped"], "-2.8 18.1 15.3": ["frostnip"], "14.8 1.8 0.7": ["videowall"], "4.2 -2.0 15.0": ["gazar"], "12.9 8.9 17.0": ["prehuman"], "18.3 7.6 22.1": ["hinny"], "-2.1 6.6 5.8": ["ddd"], "-4.8 1.8 9.8": ["cyanocobalamin"], "10.9 4.9 8.1": ["madeup"], "-6.1 6.2 11.0": ["youu"], "17.7 3.1 11.6": ["umentary"], "5.8 9.0 15.9": ["hanna"], "2.0 2.5 13.9": ["antonio"], "15.3 35.3 14.6": ["lycans"], "6.0 9.3 8.6": ["halfime", "kloof"], "3.9 -4.1 8.5": ["pregnenolone"], "10.6 3.8 1.4": ["proctology"], "15.8 5.2 22.6": ["restraunt"], "-1.8 1.0 6.1": ["ancy"], "15.1 6.0 11.5": ["refulgent"], "1.9 15.6 15.8": ["miticide"], "-2.4 3.2 1.8": ["deos"], "9.6 11.9 9.3": ["uninvestable"], "-0.8 19.4 5.5": ["kennelmate"], "12.2 13.9 9.7": ["vampyre"], "15.8 14.6 9.6": ["bisection"], "-10.5 10.7 -5.4": ["revelant"], "10.4 12.9 4.9": ["monthes"], "4.3 1.4 4.6": ["polyaniline"], "9.7 12.9 1.6": ["controler"], "4.4 0.0 9.1": ["lunes"], "2.9 21.8 12.3": ["storywise"], "4.6 14.6 5.3": ["numerics"], "11.5 27.0 7.5": ["phantasmic"], "20.3 17.4 5.7": ["electrosmog"], "4.8 4.4 3.4": ["relamping"], "5.8 13.2 17.1": ["malodor"], "4.4 17.8 17.8": ["inarticulately"], "5.2 7.6 9.3": ["obturator"], "6.8 9.2 43.9": ["scoter"], "3.7 14.8 11.7": ["antismuggling"], "8.4 6.7 20.0": ["mophead"], "1.5 3.8 14.4": ["therafter"], "8.9 7.7 31.0": ["dodol"], "19.5 11.5 4.9": ["aross"], "18.5 -3.1 7.4": ["delux"], "4.9 18.1 7.5": ["prehaps"], "4.1 6.1 7.9": ["readapted"], "12.6 27.9 11.6": ["vanquishers"], "16.8 17.7 13.6": ["randomizer"], "0.4 17.2 17.8": ["magnus"], "6.9 3.2 6.2": ["pourakarmikas"], "4.8 5.4 12.2": ["nonmajors"], "20.8 14.7 16.6": ["greenpeace"], "1.2 6.1 10.3": ["veddy"], "14.1 17.1 9.8": ["roguishly"], "2.9 14.9 9.3": ["khoon"], "12.7 2.7 -2.6": ["francise"], "4.3 -11.8 -3.4": ["bvba"], "3.4 7.9 -0.6": ["autoevolution"], "2.8 6.4 22.2": ["sorghums"], "-1.4 6.7 11.0": ["nitration"], "14.9 8.3 15.7": ["oso"], "5.9 23.7 21.8": ["datu"], "13.1 7.7 2.7": ["autotuning"], "0.1 10.6 8.1": ["lado"], "-4.7 -0.7 0.2": ["venography"], "6.6 4.0 7.9": ["sitt"], "16.6 9.2 14.7": ["fixit"], "16.2 5.9 18.5": ["mitres"], "-0.6 10.1 0.8": ["susses"], "-0.5 1.3 -3.0": ["tomrrow"], "2.8 21.4 6.1": ["yemen"], "9.7 4.9 20.7": ["fireclay"], "10.4 11.9 19.5": ["odorata"], "27.2 6.7 8.2": ["bazillionaire"], "8.5 0.6 12.9": ["carta"], "-2.0 13.1 7.1": ["rephrases"], "5.1 7.3 14.5": ["plagioclase"], "3.5 16.5 12.8": ["finna"], "14.6 7.6 21.7": ["loong"], "-1.9 15.4 11.7": ["arbovirus"], "11.7 16.3 16.6": ["midships"], "2.4 3.8 30.3": ["insalata"], "1.2 10.8 4.9": ["teching"], "5.5 8.9 13.8": ["subfloors"], "5.9 21.3 23.1": ["unfertile"], "0.2 19.3 6.7": ["deadtime"], "-6.8 10.7 11.1": ["arboviruses"], "5.5 7.4 12.5": ["dishabille"], "-1.2 11.0 7.3": ["ubiquinol"], "15.1 1.2 25.1": ["alfajores"], "12.1 5.3 17.4": ["wawa"], "3.5 14.0 10.9": ["quartiers"], "8.9 16.1 13.3": ["brokeback"], "13.0 9.5 7.5": ["counterprogram"], "22.6 6.8 9.1": ["swallowable"], "2.0 -6.5 19.3": ["laminaria"], "-6.5 5.8 6.7": ["thyrotropin"], "21.4 9.1 9.9": ["websurfers"], "9.0 12.5 15.6": ["haloing"], "-4.0 22.5 1.8": ["charactor"], "0.2 8.8 3.8": ["mattter"], "13.3 20.4 8.0": ["huns"], "13.3 7.5 1.8": ["surpising"], "7.1 6.2 39.1": ["matsutakes"], "-2.1 17.7 10.3": ["adlibbed"], "-4.7 17.2 7.2": ["immmediately"], "2.3 2.2 0.4": ["tranferring"], "12.7 7.9 29.0": ["achar"], "3.4 9.1 12.6": ["consis"], "23.8 -0.5 14.0": ["plinked"], "3.1 -0.9 6.7": ["retour"], "10.6 20.4 4.3": ["compassing"], "7.3 5.9 17.4": ["aronia"], "5.4 9.7 8.6": ["bustee"], "-0.1 -0.0 10.1": ["cranioplasty"], "5.5 13.7 7.7": ["quiter"], "30.8 10.0 19.4": ["sumos"], "0.6 9.4 4.0": ["andour"], "2.8 3.1 5.7": ["multiaxial"], "10.7 13.0 40.7": ["spearfishermen"], "21.3 5.9 8.1": ["verion"], "6.7 3.0 17.3": ["onli"], "-3.3 4.2 11.3": ["subtyped"], "5.2 13.6 2.9": ["assett"], "-0.7 4.5 3.3": ["villes"], "10.0 1.5 8.2": ["gearshifter"], "-8.6 9.1 8.1": ["leukocytosis"], "15.4 13.3 12.0": ["termagant"], "9.1 9.6 4.2": ["nanobattery"], "8.6 7.7 8.1": ["illeagal"], "3.4 6.5 11.2": ["tsismis"], "13.8 4.6 10.5": ["rearchitecting"], "15.0 22.4 21.0": ["unsmilingly"], "-6.9 2.5 0.9": ["isatoribine"], "16.6 15.5 13.9": ["slidey"], "-1.9 4.1 2.5": ["pathognomonic"], "19.4 6.8 16.9": ["clapperboard"], "2.7 5.2 15.3": ["piya"], "11.9 4.5 4.0": ["xm"], "2.5 15.0 8.3": ["lipservice"], "9.9 13.2 3.9": ["capturer"], "1.9 15.4 14.7": ["mineralizations"], "10.1 -1.7 3.1": ["roughtly"], "6.5 7.5 24.6": ["epimedium"], "3.4 4.1 4.6": ["flecainide"], "6.1 24.4 8.0": ["decieving"], "5.3 6.4 9.8": ["mobisites"], "13.7 9.2 12.7": ["ballade"], "2.1 10.4 8.8": ["speling"], "5.9 6.7 10.3": ["infectors"], "3.9 9.8 0.2": ["transthoracic"], "11.3 16.7 7.4": ["uhuru"], "24.9 8.5 23.4": ["taniwha"], "10.3 32.6 11.5": ["seditions"], "22.3 10.4 35.4": ["grapnel"], "13.2 21.9 10.1": ["hummm"], "5.7 8.4 -1.2": ["explaing"], "9.3 9.7 12.7": ["superboat"], "10.4 5.2 4.9": ["outleapt"], "5.7 19.2 7.7": ["anticlericalism"], "1.3 5.1 8.7": ["concessioners"], "12.1 9.4 11.3": ["globo"], "6.5 2.0 16.8": ["squalane"], "8.8 23.5 13.2": ["ritualist"], "10.1 11.5 18.6": ["aquanaut"], "9.4 6.4 8.2": ["linescores"], "3.0 0.2 14.7": ["shotclock"], "-0.1 -6.8 4.7": ["physiatry"], "12.6 16.2 9.8": ["webgame"], "5.9 18.5 10.8": ["likin"], "9.9 -2.0 11.6": ["crobar"], "4.7 18.2 6.1": ["trilaterally"], "12.8 16.9 30.9": ["bulblets"], "13.1 11.0 9.2": ["trifocals"], "-2.5 3.9 3.9": ["busulfan"], "11.7 -6.0 7.0": ["pany"], "2.7 6.2 12.3": ["intersexual"], "8.0 17.1 15.1": ["wheelhouses"], "15.0 14.4 9.2": ["unfetter"], "6.7 11.4 2.9": ["metatag"], "10.7 13.1 17.9": ["moonbow"], "10.6 0.9 25.3": ["goaty"], "7.7 8.0 9.1": ["beatmaking"], "7.9 0.2 44.6": ["blueback"], "15.1 8.0 12.4": ["basball"], "12.9 13.5 10.9": ["swipers"], "-3.4 -6.2 -1.5": ["tte"], "5.9 10.3 8.3": ["misaddressed"], "4.8 13.4 12.2": ["bicarbonates"], "12.3 15.5 11.8": ["partsmakers"], "1.4 10.5 3.4": ["reinduction"], "17.0 10.7 13.7": ["athons"], "-0.4 20.8 8.6": ["adultry"], "14.6 7.9 6.6": ["qatar"], "11.7 4.9 4.1": ["pattycake"], "9.3 8.7 14.7": ["pelitic"], "-0.3 0.1 1.4": ["nded"], "0.8 11.8 7.0": ["homiletic"], "-3.4 -9.9 0.7": ["preadmission"], "19.2 15.1 14.9": ["semifamous"], "8.3 21.1 6.0": ["psychs"], "4.1 13.7 5.4": ["previz"], "5.1 1.8 -0.4": ["newark"], "10.8 9.8 14.0": ["dowdiness"], "8.0 23.6 23.5": ["coastlands"], "6.5 14.0 16.0": ["osteocytes"], "9.5 10.4 21.2": ["taxonomical"], "8.4 17.1 14.0": ["microelectrode"], "6.5 3.3 17.6": ["meatworker"], "4.2 2.6 11.9": ["methylcellulose"], "11.5 13.7 9.0": ["hotwater"], "-0.3 2.6 3.0": ["distruption"], "3.8 14.3 8.3": ["pushout"], "-8.4 1.0 2.7": ["atrisk"], "11.0 1.6 14.7": ["areolas"], "5.1 7.9 12.7": ["diminutives"], "4.7 18.0 8.2": ["miskicking"], "6.7 10.4 13.0": ["dustjacket"], "-5.5 13.6 5.4": ["primaquine"], "-0.3 0.1 0.3": ["chandigarh"], "1.5 8.6 4.0": ["jav"], "-4.1 27.8 0.3": ["unknow"], "2.9 -0.2 8.0": ["informationon"], "8.8 31.3 12.7": ["immoderation"], "0.8 10.0 1.7": ["fipamezole"], "14.7 9.4 10.1": ["cyberslacking"], "8.5 16.4 13.1": ["orton"], "-4.6 1.2 8.3": ["dz"], "5.0 1.7 8.1": ["underrecovery"], "12.7 8.0 21.7": ["pointbreak"], "13.9 3.8 31.8": ["halushki"], "-0.0 5.1 20.1": ["mawa"], "13.7 9.9 11.5": ["typecasts"], "5.0 16.7 2.9": ["toprevent"], "23.2 6.7 1.4": ["renationalising"], "-5.5 -5.4 4.2": ["kus"], "6.6 16.2 16.7": ["plighted"], "14.1 14.4 13.6": ["dingiest"], "8.1 18.6 12.5": ["pluggin"], "-7.7 19.7 9.5": ["suspendable"], "3.7 24.0 9.8": ["metta"], "-2.5 6.0 16.6": ["gihapon"], "13.4 14.6 15.7": ["footstone"], "23.1 9.4 19.4": ["zithers"], "9.7 -1.9 3.5": ["topamax"], "-3.2 28.3 12.8": ["callee"], "14.2 6.5 11.6": ["cheaping"], "4.4 10.4 12.8": ["recombinations"], "0.4 6.8 25.0": ["brunello"], "12.6 16.6 9.3": ["bugled"], "12.6 7.4 16.6": ["rastas"], "16.1 10.8 15.7": ["patten"], "9.3 5.1 10.2": ["stade"], "6.5 -5.3 7.8": ["doube"], "15.5 10.7 9.6": ["grungiest"], "13.3 20.7 10.8": ["kindlier"], "10.1 20.9 7.3": ["secluding"], "24.8 -0.8 24.2": ["stockpots"], "14.2 16.9 10.3": ["fibrillating"], "5.4 13.2 11.4": ["romanization"], "16.3 25.0 15.6": ["spitfires"], "4.2 2.8 4.3": ["newssheet"], "-1.8 7.5 1.2": ["thirdround"], "2.4 -4.5 0.8": ["acr"], "0.8 6.6 7.7": ["manteau"], "0.7 18.8 10.2": ["newphew"], "3.7 18.3 -0.4": ["nonhierarchical"], "-3.6 16.4 -6.7": ["exfiltrated"], "-4.0 3.2 7.0": ["reedist"], "7.6 18.5 20.1": ["quebrada"], "26.1 10.9 6.9": ["skywriter"], "25.4 -1.3 -10.0": ["unveilled"], "11.8 34.8 9.5": ["ratlines"], "9.7 -2.9 6.0": ["writebacks"], "16.8 11.2 26.9": ["exclosure"], "2.6 3.8 12.7": ["raas"], "0.5 20.3 5.2": ["sayed"], "6.8 10.0 2.2": ["informationally"], "6.7 10.8 13.4": ["inconel"], "12.4 5.6 5.6": ["websurfing"], "4.7 16.4 12.7": ["epicardium"], "9.2 16.9 -2.9": ["toprotect"], "15.7 14.5 31.7": ["flowerheads"], "7.0 13.4 9.9": ["wallowy"], "-1.8 7.7 11.2": ["sach"], "-2.1 6.8 -3.9": ["worke"], "5.4 3.7 9.3": ["reglazing"], "5.8 22.3 5.7": ["polit"], "14.0 18.8 7.3": ["memetic"], "12.4 2.8 20.4": ["husker"], "11.5 13.2 8.5": ["microjet"], "9.8 10.5 13.7": ["lesbos"], "14.4 5.3 14.4": ["engravable"], "3.9 26.5 6.6": ["armorers"], "10.9 3.9 13.8": ["posto"], "-5.8 9.4 5.1": ["babyproofing"], "6.4 21.5 9.4": ["enfeeblement"], "-1.2 2.6 10.2": ["untallied"], "-2.9 -1.9 -0.0": ["microfarads"], "6.3 -2.1 15.1": ["ashland"], "2.5 11.6 0.9": ["encomia"], "6.3 9.3 16.8": ["scheds"], "-2.2 -2.1 6.5": ["thyroxin"], "5.2 6.9 11.5": ["pheomelanin"], "10.8 3.0 7.6": ["afta"], "0.2 9.7 4.8": ["neurosyphilis"], "-0.7 13.0 11.9": ["importanly"], "-4.5 10.5 6.9": ["midsemester"], "7.7 -1.9 8.4": ["stearate"], "13.4 5.4 3.9": ["brandhouse"], "-0.3 14.7 5.0": ["cornerkicks"], "2.1 12.7 0.2": ["havans"], "-4.5 3.9 5.5": ["bisoprolol"], "11.8 2.9 21.0": ["toiles"], "3.0 10.1 10.2": ["singspiel"], "10.1 15.3 16.6": ["causer"], "1.1 20.3 -5.3": ["benificial"], "17.0 27.6 2.4": ["destructors"], "5.0 10.5 15.1": ["unsaddling"], "-2.3 -9.1 -2.6": ["oncampus"], "7.7 23.8 13.7": ["thosewho"], "12.3 29.4 4.9": ["triumphalists"], "-7.0 15.8 5.0": ["nondischargeability"], "2.3 6.6 5.7": ["indentureship"], "-0.4 12.4 -3.8": ["capablities"], "14.3 8.5 7.0": ["waggishly"], "0.9 0.4 -6.7": ["neurotherapy"], "2.9 8.2 -8.7": ["organistaion"], "1.2 12.8 5.7": ["castigations"], "10.2 13.0 10.9": ["screenies"], "7.1 7.0 8.0": ["geri"], "11.4 34.0 8.6": ["supervillian"], "3.7 8.8 8.3": ["nitriding"], "15.0 5.4 25.6": ["skelton"], "-10.7 -0.7 2.1": ["antiepileptics"], "5.3 13.2 6.7": ["antigenicity"], "-2.1 16.5 3.0": ["determind"], "-2.9 8.7 -5.3": ["alled"], "-0.3 16.6 12.9": ["grabed"], "0.2 8.9 10.4": ["emmission"], "-4.2 6.3 5.4": ["spectrophotometric"], "4.0 7.0 21.9": ["mammalogist"], "-0.5 19.6 5.8": ["acomplished"], "15.4 0.2 3.9": ["promot"], "11.7 -5.4 21.9": ["brewfest"], "0.1 15.5 23.8": ["kitniyot"], "11.0 4.1 22.9": ["tabi"], "-4.6 2.9 -0.7": ["prn"], "4.2 5.6 14.5": ["eggings"], "9.4 5.3 30.9": ["deadrise"], "11.8 7.1 18.8": ["estilo"], "-4.3 -3.3 0.0": ["subconsultants"], "4.3 7.5 2.9": ["empassioned"], "17.6 21.9 18.6": ["binocs"], "17.7 -0.9 15.4": ["sourcer"], "0.5 -0.9 10.1": ["mised"], "9.9 -4.9 13.3": ["clothbound"], "-4.0 0.1 2.1": ["hemispherectomy"], "2.6 -5.6 7.6": ["wnet"], "-5.1 10.5 -0.2": ["wcg"], "-0.1 4.0 13.5": ["neen"], "-1.6 9.7 12.2": ["decathalon"], "-1.9 6.5 15.2": ["kollox"], "7.9 5.5 9.4": ["jhola"], "10.8 4.5 5.8": ["dubber"], "16.2 27.8 16.5": ["devourers"], "-0.4 7.5 10.9": ["collations"], "11.7 19.5 12.3": ["loiterer"], "4.7 10.6 11.5": ["ologies"], "-0.5 4.0 7.4": ["precleared"], "9.7 6.7 21.0": ["barriques"], "2.8 13.6 14.3": ["surlier"], "5.6 19.4 -0.3": ["forefronts"], "13.0 10.3 21.1": ["pube"], "16.1 7.7 8.4": ["blippy"], "4.6 -5.6 12.3": ["anlayst"], "-3.4 2.0 5.2": ["aban"], "9.1 9.7 -3.5": ["dilations"], "5.5 13.5 -0.7": ["dinned"], "-4.4 -5.3 3.5": ["licensures"], "0.6 9.8 4.5": ["gayaki"], "0.7 6.4 2.6": ["befrienders"], "5.6 -0.8 1.7": ["webservices"], "11.8 20.1 19.6": ["greatcoats"], "-6.8 8.8 3.9": ["impeccability"], "13.4 1.6 -1.2": ["workes"], "8.1 12.5 -2.7": ["accesss"], "4.9 -9.1 5.4": ["kinesiologists"], "15.0 13.4 17.2": ["belfries"], "14.7 9.5 10.3": ["archaelogists"], "8.8 24.9 10.5": ["imperturbability"], "14.9 10.2 15.9": ["dimestore"], "2.3 12.2 6.9": ["misconnection"], "8.4 1.7 8.6": ["covermounts"], "9.2 17.3 9.6": ["sybarite"], "16.5 6.8 5.9": ["momentus"], "15.7 12.9 14.8": ["daftly"], "9.7 11.4 -2.2": ["blats"], "8.3 9.9 2.5": ["sucessive"], "17.9 10.4 21.3": ["caecilian"], "2.0 8.7 -0.9": ["predecesor"], "7.8 22.1 10.1": ["ukase"], "2.8 17.2 3.6": ["expostulated"], "7.0 6.6 10.6": ["stultifyingly"], "-0.6 17.3 17.7": ["unselective"], "1.0 7.7 11.4": ["selenoproteins"], "10.9 -7.5 1.3": ["peforms"], "13.9 -3.8 4.8": ["signwriting"], "4.5 5.1 1.3": ["retreader"], "5.8 20.2 -4.1": ["quesion"], "23.3 20.8 15.6": ["dropkicking"], "16.0 2.0 6.7": ["trashings"], "7.2 22.7 15.0": ["equivocator"], "19.7 6.1 12.5": ["quadcore"], "0.5 7.7 10.4": ["coactivator"], "1.5 4.4 7.0": ["ror"], "14.6 18.6 10.0": ["piracies"], "17.3 6.7 33.9": ["pogey"], "15.4 11.4 20.5": ["underplanted"], "12.3 7.5 1.0": ["goverance"], "0.7 9.6 13.9": ["luer"], "13.3 3.8 26.1": ["bicolored"], "15.1 17.1 7.8": ["infector"], "2.7 1.9 8.0": ["photogravures"], "8.1 6.2 11.6": ["calisthenic"], "1.8 16.0 0.7": ["kabaka"], "7.0 9.8 11.0": ["postfix"], "-4.2 0.7 1.6": ["ontact"], "3.2 3.6 3.1": ["seguir"], "20.5 3.1 14.4": ["shoji"], "7.8 11.5 8.8": ["bise"], "15.1 20.8 6.8": ["worshipfully"], "4.7 13.9 9.1": ["jaisa"], "0.2 12.0 15.5": ["ginsenosides"], "3.3 4.7 10.2": ["annualise"], "6.2 7.9 11.4": ["densifying"], "3.2 5.6 9.1": ["pysch"], "5.2 12.5 3.6": ["meteo"], "10.2 5.9 13.1": ["bomas"], "15.0 15.7 9.7": ["frightener"], "11.5 5.4 17.6": ["coldstore"], "-3.5 6.7 4.5": ["gehen"], "-7.0 2.1 2.6": ["satsangs"], "9.7 25.8 3.8": ["spys"], "7.8 10.9 11.9": ["unhelmeted"], "12.5 7.6 15.5": ["pollard"], "9.0 18.7 3.5": ["populistic"], "5.1 41.1 2.1": ["mujahids"], "-10.3 11.6 2.4": ["exegete"], "10.1 8.6 50.9": ["opah"], "14.0 6.7 12.1": ["ablates"], "3.8 9.9 4.6": ["eponyms"], "13.6 15.4 15.3": ["rabbity"], "-4.6 7.0 10.1": ["hypofractionated"], "7.8 4.4 13.1": ["roughies"], "12.2 13.3 17.3": ["esker"], "10.4 12.2 7.1": ["dropsonde"], "-1.8 20.1 8.5": ["defenitely"], "16.1 -1.6 -0.8": ["acrosss"], "17.3 7.4 13.9": ["overnite"], "-3.7 0.3 3.2": ["principalships"], "18.5 7.9 27.9": ["monopiles"], "3.5 4.6 9.6": ["denne"], "17.4 -3.3 21.8": ["venetian"], "11.6 3.8 8.3": ["nonsolicitation"], "6.1 11.2 4.7": ["cked"], "2.5 -5.1 -8.8": ["eca"], "7.9 18.8 6.5": ["propogating"], "-7.8 2.1 -3.2": ["relevation"], "1.9 8.5 -2.7": ["ancrod"], "8.1 8.1 7.6": ["lambert"], "22.0 10.4 18.9": ["chainlink"], "2.0 20.4 10.4": ["ammos"], "3.3 8.1 3.5": ["basolateral"], "13.3 9.6 22.5": ["greenware"], "14.0 10.3 8.9": ["geotechnology"], "5.7 -5.6 6.4": ["soir"], "15.8 12.7 -3.8": ["whisteblower"], "7.0 16.3 2.8": ["apocalypticism"], "11.0 19.5 18.2": ["whipworms"], "-2.7 7.3 6.1": ["informe"], "10.1 14.6 -4.7": ["suporting"], "2.3 3.8 25.7": ["pedas"], "-9.0 8.3 3.0": ["postdischarge"], "12.6 9.8 23.1": ["skat"], "3.6 9.7 4.6": ["sideroads"], "0.7 3.2 0.7": ["andinformation"], "7.7 5.1 25.1": ["libreta"], "24.5 5.5 19.1": ["overbloated"], "-5.1 27.6 -2.7": ["surrendees"], "14.3 -5.4 16.7": ["ladie"], "7.0 18.2 7.0": ["pasengers"], "5.2 12.4 12.2": ["muchly"], "0.5 2.1 1.5": ["distrcit"], "8.8 3.5 12.9": ["lacemaking"], "7.2 9.4 21.8": ["creekbeds"], "14.6 13.4 14.3": ["libra"], "-4.0 11.8 10.1": ["simazine"], "7.8 4.7 10.8": ["gwen"], "10.2 17.9 6.0": ["colonialisation"], "4.8 -0.2 -1.0": ["trivago"], "-2.8 12.5 8.5": ["paraphilias"], "3.7 4.5 26.4": ["skijor"], "19.4 12.7 29.8": ["meadowsweet"], "18.2 15.7 9.5": ["creakily"], "-2.4 6.2 10.5": ["jumpouts"], "14.5 6.2 11.4": ["beon"], "5.3 10.7 5.3": ["chmod"], "1.7 14.8 3.9": ["resons"], "1.3 4.6 4.1": ["parler"], "1.5 12.2 9.2": ["ananda"], "12.4 6.1 13.2": ["guiderails"], "9.4 2.9 15.1": ["radiused"], "11.2 0.4 3.3": ["surronding"], "14.4 19.3 8.9": ["someways"], "4.8 12.7 20.3": ["sparmates"], "17.0 20.3 17.6": ["birdbrains"], "12.2 20.6 10.0": ["smark"], "2.5 15.1 3.0": ["mapatumumab"], "0.9 11.0 9.0": ["supermotard"], "-1.1 0.1 2.9": ["eighthgrade"], "13.7 6.8 2.4": ["bonafied"], "8.0 8.1 -2.5": ["rockingest"], "-10.8 9.1 10.4": ["alachlor"], "2.1 9.0 15.3": ["cysteines"], "10.1 10.3 8.3": ["ricochetted"], "7.0 18.5 -3.6": ["strenthening"], "25.2 14.7 19.7": ["crenelated"], "18.0 19.8 6.3": ["foreshadowings"], "-0.6 18.1 -2.1": ["panth"], "-0.4 8.3 5.4": ["vob"], "6.2 8.5 5.1": ["nagarpalikas", "sigmoidal"], "6.6 12.0 15.8": ["claystone"], "1.3 15.0 7.7": ["offstride"], "7.4 5.6 13.9": ["delts"], "4.5 4.5 22.8": ["homecooking"], "13.4 5.2 13.5": ["boardsport"], "9.2 9.3 10.7": ["caffiene"], "-1.0 5.0 3.6": ["judicatory"], "12.8 6.4 4.1": ["possble"], "10.4 9.9 2.7": ["underowned"], "7.4 10.1 8.3": ["museological"], "6.4 -4.9 -3.3": ["ener"], "2.3 30.0 4.3": ["defamers"], "11.1 4.6 13.2": ["nipplegate"], "3.4 10.0 14.2": ["aperiodic"], "8.3 11.4 20.3": ["offies"], "6.1 3.9 19.1": ["woodturners"], "11.1 23.8 13.3": ["blamers"], "6.2 28.9 12.9": ["armers"], "11.2 29.2 8.3": ["appeasements"], "12.1 6.5 13.4": ["luz"], "9.2 5.8 16.2": ["douce"], "18.2 8.6 17.8": ["charlies"], "11.4 8.3 7.5": ["busmen"], "12.6 3.9 20.7": ["barback"], "11.7 9.7 17.2": ["boxspring"], "18.2 15.0 9.7": ["suiters"], "7.7 23.7 13.7": ["miscall"], "2.5 3.8 12.5": ["faj"], "16.1 12.0 19.4": ["micronations"], "-5.7 -4.7 2.9": ["emda"], "2.1 -1.9 1.6": ["downblending"], "2.6 16.5 5.7": ["epical"], "28.5 31.8 20.5": ["homunculi"], "5.3 9.0 7.5": ["disaccharide"], "-10.1 7.6 -2.1": ["professionality"], "2.6 20.0 13.6": ["reductionistic"], "8.0 9.6 -1.3": ["earthshattering"], "5.9 19.5 15.6": ["blockouts"], "7.9 14.7 16.7": ["colugos"], "12.3 11.9 13.7": ["literately"], "13.8 15.7 11.4": ["balseros"], "0.1 -7.4 0.2": ["embolotherapy"], "4.4 12.2 10.0": ["summitting"], "14.9 9.2 19.3": ["chesnut"], "6.0 4.3 16.2": ["leonard"], "12.2 26.8 6.2": ["manouvering"], "3.4 3.9 0.9": ["inaccordance"], "6.1 -0.1 -2.4": ["applicaton"], "1.7 -1.0 3.3": ["tates"], "15.6 12.2 14.3": ["spermatozoon"], "0.2 -2.3 9.0": ["nish"], "12.0 -0.7 11.4": ["takeways"], "4.9 8.0 15.7": ["blogdom"], "0.5 -7.1 1.7": ["atr"], "10.9 10.5 22.9": ["locoweed"], "3.2 -5.3 5.6": ["rik"], "-2.5 1.0 9.5": ["ently"], "21.7 1.9 13.3": ["sawmiller"], "3.3 2.7 5.2": ["nonpublished"], "3.8 10.7 11.6": ["terranes"], "5.7 12.7 15.9": ["bobnjersey"], "5.2 13.6 3.2": ["vechicles"], "17.3 12.5 16.0": ["dreg"], "5.6 13.2 14.2": ["fermentor"], "4.1 17.2 8.1": ["thirdand"], "20.0 11.8 19.9": ["liverwort"], "-6.2 -4.0 8.8": ["practica"], "4.3 7.4 -6.6": ["officails"], "4.6 10.5 6.3": ["ribonuclease"], "-0.3 4.4 12.5": ["remo"], "8.6 12.8 12.4": ["daisycutter"], "7.0 23.9 15.2": ["highwalls"], "2.5 1.0 8.9": ["lyon"], "2.1 10.9 31.5": ["wildfowling"], "8.7 18.0 16.5": ["frizzies"], "10.7 29.4 20.1": ["domineer"], "3.1 19.5 -2.0": ["depoliticising"], "11.9 2.1 2.0": ["enduced"], "10.3 12.5 15.4": ["haulin"], "-0.6 10.6 15.3": ["eleksyon"], "3.7 8.0 11.4": ["paratuberculosis"], "-10.2 -1.7 6.9": ["sudents"], "-3.2 11.3 18.6": ["sensitve"], "18.0 3.7 7.9": ["setto"], "15.4 7.7 17.1": ["dishrags"], "18.1 7.2 16.0": ["slidin"], "9.7 -1.4 10.1": ["upholsteries"], "0.2 0.3 4.1": ["andra"], "21.1 23.7 23.4": ["chiclet"], "9.7 11.7 7.3": ["myraptureplaylist"], "11.1 7.7 15.5": ["harmonizers"], "25.5 14.6 25.0": ["baobabs"], "13.8 14.8 13.8": ["nuc"], "2.7 -7.7 3.6": ["aprile"], "10.9 -0.5 4.7": ["undercapacity"], "-5.3 0.9 4.4": ["admittances"], "9.8 3.4 -7.3": ["alllow"], "-4.4 8.6 2.9": ["shri"], "10.7 12.5 12.3": ["stolidity"], "4.0 0.7 4.6": ["postmarking"], "-0.4 22.8 7.3": ["expressible"], "6.7 21.6 10.1": ["oursleves"], "8.9 15.3 5.1": ["gaul"], "-2.8 19.6 7.0": ["reeducating"], "13.4 15.9 7.2": ["quested"], "15.6 4.4 26.1": ["cruets"], "8.2 6.6 13.8": ["protesta"], "2.4 15.6 16.4": ["contemplatives"], "3.6 25.5 14.1": ["bioagents"], "-0.5 8.0 4.1": ["uptodate"], "7.7 19.3 15.3": ["disapear"], "24.6 15.5 18.1": ["lightpost"], "9.1 1.8 12.4": ["contradance"], "-0.8 3.7 8.8": ["cially"], "2.8 5.9 16.8": ["reairing"], "0.9 12.0 -0.8": ["reassumes"], "4.5 -1.1 6.1": ["iimia"], "-0.8 3.0 12.0": ["suporta"], "11.3 12.7 26.1": ["mopheads"], "4.7 1.0 10.7": ["syracuse"], "6.8 1.2 2.0": ["gigapixels"], "14.7 15.6 17.1": ["petrification"], "5.4 11.9 10.6": ["eleemosynary"], "2.3 9.9 7.5": ["yoruba"], "6.7 -2.6 -0.2": ["webbased"], "3.5 19.4 0.0": ["postrevolutionary"], "2.2 7.9 18.7": ["recissions"], "3.1 5.5 9.2": ["lightheavyweight"], "11.7 5.9 14.1": ["pantaloon"], "5.8 8.3 10.4": ["paralyzation"], "7.8 6.0 9.0": ["deskilling"], "-2.5 14.4 0.9": ["percipient"], "2.8 1.2 18.2": ["hanseboot"], "12.9 14.6 0.2": ["transmogrifies"], "-2.0 5.7 8.9": ["microglial"], "7.1 5.9 11.8": ["rhyodacite"], "4.6 11.2 18.7": ["moro"], "6.6 2.4 17.2": ["joanna"], "2.3 5.9 11.2": ["guiders"], "7.3 8.5 13.1": ["nostra"], "6.0 6.6 4.4": ["quartefinals"], "11.9 6.2 13.0": ["noseband"], "-0.9 2.9 6.3": ["indibulin"], "-0.9 18.5 9.6": ["multiculturally"], "0.5 1.5 2.5": ["threshholds"], "-2.2 11.9 12.5": ["iritis"], "1.4 10.3 -8.4": ["gazeta"], "1.4 0.9 14.1": ["dorothy"], "5.4 -1.7 -12.4": ["apearance"], "7.3 2.6 -1.0": ["overclaiming"], "10.9 8.3 38.1": ["rabe"], "9.6 29.5 3.5": ["iranians"], "8.3 3.7 20.4": ["paddlewheelers"], "8.5 -3.5 20.8": ["appley"], "1.2 7.9 3.1": ["thorazine"], "16.0 14.9 14.4": ["spyder"], "4.1 2.7 19.6": ["calvings"], "10.0 31.5 12.7": ["villainesses"], "16.1 2.9 4.0": ["sistemas"], "15.1 1.2 7.7": ["downlaod"], "12.1 1.4 -1.9": ["autopay"], "2.5 9.9 14.1": ["alimentation"], "1.5 2.3 -1.8": ["ameeting"], "10.3 8.1 10.8": ["longhole"], "3.3 9.6 18.6": ["barleywines"], "19.3 10.2 23.7": ["chasse"], "7.9 4.1 11.3": ["washery"], "-2.4 9.2 3.8": ["sarcomatoid"], "3.8 -3.1 6.9": ["uncataloged"], "5.8 20.7 3.8": ["retconned"], "8.1 9.3 19.7": ["duneland"], "18.6 0.7 10.2": ["alky"], "10.0 27.4 10.6": ["mudslinger"], "12.6 0.2 16.5": ["foofy"], "10.6 12.2 0.7": ["raper"], "1.8 -5.3 -1.9": ["direc"], "0.1 7.4 3.8": ["baraza"], "17.5 20.6 13.2": ["equilateral"], "3.6 33.0 0.7": ["offencive"], "7.3 6.2 6.2": ["ftr"], "7.2 13.6 7.1": ["footchase"], "4.6 15.5 13.3": ["snottiness"], "8.7 14.2 6.3": ["amygdale"], "3.9 16.5 8.3": ["sanyasis"], "4.7 2.8 7.9": ["prakash"], "13.1 9.8 5.8": ["stumblings"], "10.7 7.7 6.9": ["showmanlike"], "5.9 13.1 5.4": ["reasses"], "17.2 20.4 11.6": ["fusebox"], "2.1 13.5 2.5": ["chokey"], "9.0 0.9 16.2": ["pount"], "-2.1 18.0 7.1": ["arein"], "3.9 10.1 -0.9": ["recognizers"], "9.5 5.5 15.2": ["repacks"], "-3.3 8.3 1.7": ["splitted"], "11.2 20.4 3.4": ["inmy"], "0.5 8.0 13.5": ["chanda"], "1.8 28.6 -3.9": ["genocidaire"], "10.3 6.5 3.0": ["agroup"], "3.8 9.3 10.5": ["webhosts"], "8.8 19.8 16.8": ["puckhandler"], "4.4 12.3 14.6": ["manus"], "-2.0 9.7 12.9": ["aeruginosa"], "5.0 6.0 4.2": ["micellar"], "0.4 2.9 15.8": ["darsan"], "16.2 22.6 15.8": ["sanguinely"], "10.0 13.8 17.3": ["geiko", "bunkie"], "23.0 12.7 25.9": ["frolickers"], "5.4 12.2 4.7": ["tokunbo"], "3.6 12.4 7.1": ["crazyforchelsea"], "-1.4 5.2 4.5": ["chucktodd"], "21.7 1.4 7.6": ["onsell"], "11.9 6.6 8.8": ["ymail"], "5.8 17.6 11.3": ["tallent"], "-2.8 11.7 10.1": ["exgirlfriend"], "2.3 24.4 12.6": ["theys"], "3.8 10.7 22.5": ["microbiomes"], "-2.4 7.2 17.8": ["unsewered"], "3.9 3.8 9.8": ["trochanter"], "7.6 8.3 -3.4": ["dematerialise"], "1.6 11.1 0.8": ["mortgager"], "3.7 7.7 7.8": ["mitumba"], "13.0 7.5 28.0": ["leucistic"], "14.0 17.0 13.8": ["valenki"], "-5.7 6.0 9.0": ["zyada"], "18.1 -9.8 7.3": ["bezier"], "15.5 26.0 33.1": ["kingbird"], "28.0 12.6 15.0": ["wibble"], "9.2 3.5 16.6": ["hominoid"], "8.8 5.7 7.1": ["delgates"], "-2.4 7.3 -3.8": ["closetted"], "7.5 32.9 15.1": ["guildmates"], "3.4 11.0 16.9": ["expertization"], "3.5 17.5 7.6": ["gendering"], "4.2 16.2 2.5": ["neuroprosthetics"], "5.8 14.0 0.1": ["autothrottle"], "-0.1 13.3 3.3": ["destoolment"], "-0.1 9.9 5.7": ["softtop"], "11.1 3.7 20.8": ["quoins"], "0.1 5.9 8.3": ["baselayer"], "-5.8 4.4 14.0": ["oun"], "0.7 15.3 5.3": ["psychosurgery"], "-4.4 19.1 0.1": ["reaons"], "3.6 22.8 26.1": ["houndsmen"], "16.3 4.4 13.7": ["plinky"], "6.2 4.6 27.5": ["waterview"], "5.9 24.8 12.6": ["unoffending"], "-2.3 -4.6 3.8": ["iver"], "-3.9 3.9 15.5": ["cory"], "9.0 8.3 -0.8": ["moneygram"], "6.2 9.9 15.5": ["unceded"], "3.6 7.7 19.5": ["reservior"], "1.9 -0.4 7.3": ["canciones"], "6.2 19.5 8.7": ["unfollowing"], "6.5 2.7 -7.2": ["netural"], "14.6 -5.3 5.8": ["nonconsolidated"], "6.6 11.1 13.3": ["libertad"], "-0.9 4.5 6.6": ["yakshagana"], "-0.2 -1.9 13.9": ["lts"], "8.2 11.3 16.3": ["chippier"], "-0.8 4.8 7.6": ["preconvention"], "-6.2 15.9 3.9": ["nonenforcement"], "8.6 1.0 20.8": ["wau"], "5.8 -2.5 25.8": ["kaju"], "9.2 11.3 6.1": ["besser"], "0.4 5.3 3.7": ["mosfets"], "2.9 6.9 9.1": ["crosschecker"], "-1.2 18.2 14.6": ["spaciness"], "15.2 21.7 10.8": ["sacreligious"], "5.6 19.4 5.1": ["lyse"], "-0.5 3.0 6.7": ["unbleeped"], "11.8 12.8 9.6": ["nanoprobe"], "17.4 11.6 31.8": ["plastron"], "5.3 3.2 15.9": ["hornblende"], "4.5 -4.0 3.9": ["exceled"], "1.8 3.3 12.0": ["aktar"], "6.0 10.9 12.2": ["backplay"], "11.4 16.1 28.3": ["akikiki"], "3.8 2.4 11.3": ["travelcards"], "-1.6 7.9 -0.2": ["appraisement"], "0.9 14.5 5.6": ["autoantigen"], "3.1 5.1 0.8": ["inviduals"], "0.4 -4.9 -2.9": ["eyeforpharma"], "16.5 6.1 4.1": ["thrugh"], "9.3 9.8 23.2": ["panna"], "-2.7 -0.9 6.0": ["pupilage"], "3.6 8.2 10.5": ["quadbikes"], "0.2 3.3 18.6": ["upsweep"], "7.7 10.1 12.1": ["batey"], "6.2 22.5 6.6": ["transduce"], "-5.4 5.1 12.3": ["continuted"], "13.6 16.1 11.7": ["milimetre"], "7.0 10.5 16.2": ["burt"], "16.5 0.7 16.6": ["jointer"], "12.4 6.9 -0.6": ["yearsof"], "4.5 5.2 10.2": ["imprecisions"], "3.0 19.2 7.9": ["keypresses"], "3.2 -1.9 3.5": ["bz"], "5.0 15.3 11.7": ["fumblerooskie"], "12.8 14.6 -1.5": ["extortive"], "1.6 18.1 10.6": ["eustress"], "14.8 10.8 17.2": ["risin"], "2.4 9.9 14.3": ["milega"], "12.3 16.6 12.7": ["begrudgery"], "18.1 1.7 18.0": ["augered"], "8.1 6.0 4.4": ["hostlers"], "-1.6 12.3 8.7": ["preselecting"], "2.6 1.1 26.0": ["batang"], "3.6 11.8 6.1": ["manettino"], "15.7 4.9 3.7": ["windparks"], "21.7 11.1 14.4": ["vampirish"], "2.6 12.2 2.4": ["myopericarditis"], "13.9 0.0 0.5": ["misdealings"], "4.7 7.7 19.4": ["macha"], "2.2 13.1 10.0": ["withou"], "1.3 13.8 10.8": ["pieing"], "3.3 3.1 11.8": ["xylanase"], "-0.0 14.8 17.8": ["traplines"], "1.6 10.9 7.0": ["contiued"], "1.2 14.2 11.4": ["nongenetic"], "10.9 5.7 21.6": ["barfi"], "5.8 7.3 15.8": ["hotlaps"], "0.0 2.7 0.1": ["intendant"], "-2.7 19.1 8.0": ["condemnor"], "12.0 9.3 15.1": ["turbanator"], "3.4 5.3 11.4": ["carboxyl"], "6.7 3.5 -0.4": ["subrogee"], "0.0 9.9 10.5": ["simchas"], "-3.4 9.2 11.0": ["textspeak"], "16.3 10.8 41.6": ["nicoise"], "5.3 3.6 28.4": ["patis"], "0.9 18.7 14.6": ["pugnaciousness"], "8.0 10.1 18.9": ["gaussian"], "10.2 -9.4 6.0": ["spon"], "11.0 11.6 12.1": ["frumpiness"], "3.5 -7.4 18.8": ["cach"], "5.9 -0.9 -0.2": ["colloboration"], "12.9 14.1 9.1": ["solarize"], "17.8 3.1 8.0": ["pzizz"], "18.5 14.3 13.0": ["colluders"], "10.4 2.8 3.3": ["ysterday"], "8.2 2.8 3.5": ["actuellement"], "-2.1 -0.4 6.3": ["maschera"], "-6.4 4.2 9.6": ["hepatectomy"], "-0.4 2.4 3.1": ["bullous"], "10.5 1.5 3.4": ["toledo"], "18.0 16.0 12.2": ["dizzier"], "11.0 0.1 19.4": ["speciosa"], "7.0 2.8 5.3": ["contestents"], "0.1 9.7 7.5": ["oll"], "11.2 18.7 19.6": ["putrescence"], "0.7 -0.9 10.6": ["verum"], "2.4 6.2 13.8": ["covellite"], "13.5 1.8 18.4": ["culotte"], "3.4 13.3 10.1": ["midwesterner"], "3.8 12.5 19.4": ["gerald"], "14.2 8.7 20.2": ["grasslike"], "-12.5 16.1 1.1": ["preventability"], "10.6 10.4 9.3": ["fractioned"], "6.7 10.0 4.2": ["mox"], "3.9 13.0 7.0": ["vistory"], "-0.3 13.2 4.9": ["imperativeness"], "9.0 6.9 20.9": ["baaaaad"], "-3.8 5.1 4.7": ["legionellosis"], "6.6 -4.6 10.8": ["maggio"], "-8.3 -6.4 -1.2": ["coedited"], "7.0 -5.3 14.0": ["handcrafters"], "17.4 0.9 0.0": ["datacomm"], "6.3 7.9 9.0": ["superbad"], "13.1 1.2 7.3": ["bookmarkers"], "8.0 26.6 6.7": ["boundlessness"], "4.1 5.0 12.3": ["diease"], "6.5 8.1 -0.9": ["continute"], "-3.7 12.1 4.3": ["expectance"], "4.7 3.5 1.2": ["alm"], "3.4 6.9 14.3": ["reiterative"], "5.8 13.9 11.5": ["seeingredaz"], "19.7 6.1 29.0": ["steamin"], "3.5 6.8 6.8": ["pannist"], "19.5 1.1 31.9": ["hotcake"], "1.3 17.7 4.7": ["divergently"], "7.2 20.1 4.6": ["swaggeringly"], "-5.3 10.9 6.8": ["diffucult"], "-1.0 6.5 7.8": ["revascularized"], "6.1 -0.2 9.3": ["transvestitism"], "20.0 15.9 21.3": ["gnarl"], "22.1 3.9 22.9": ["footlongs"], "12.3 19.8 13.9": ["topos"], "16.2 9.7 27.1": ["ovate"], "-2.1 16.6 5.0": ["pramukh"], "2.7 9.4 12.0": ["volleybelles"], "1.8 7.0 3.6": ["pursuiter"], "12.2 14.3 12.6": ["croud"], "6.6 4.8 24.3": ["chenilles"], "0.6 1.0 2.3": ["visist"], "3.9 10.2 14.9": ["dhavleak"], "9.4 15.4 -8.0": ["againist"], "9.4 14.8 7.2": ["commodifies"], "0.9 19.0 16.7": ["malu"], "0.8 12.6 0.4": ["tachyarrhythmia"], "1.8 5.5 18.5": ["pagkatapos"], "15.7 11.8 18.5": ["bouncin"], "11.9 13.2 15.6": ["snugness"], "13.1 9.1 19.1": ["inti"], "7.4 16.5 12.9": ["hunh"], "5.7 -0.6 9.9": ["clarsach"], "0.5 15.4 3.9": ["politbureau"], "-2.6 11.6 12.1": ["illuminative"], "-0.4 4.6 2.7": ["redcarded"], "-0.5 4.9 11.9": ["rebinding"], "6.8 9.9 17.8": ["elaborateness"], "11.7 3.0 27.2": ["hummous"], "18.9 12.6 13.3": ["chocka"], "25.6 12.0 26.7": ["furless"], "6.5 0.7 10.0": ["divalicious"], "23.0 16.7 9.3": ["spybot"], "13.1 11.9 28.7": ["lovo"], "10.0 2.2 13.2": ["bosky"], "5.0 7.9 2.1": ["docomo"], "10.0 4.9 19.8": ["propogation"], "7.6 13.9 6.9": ["grandiloquently"], "9.9 13.5 13.7": ["theie"], "17.7 4.2 9.2": ["hurd"], "14.8 13.1 21.6": ["brownness"], "16.8 4.3 -1.9": ["busness"], "7.2 1.4 9.5": ["geosteering"], "7.5 -0.0 20.9": ["noshery"], "18.7 7.4 15.4": ["spandexed"], "-0.4 4.1 6.1": ["colonoscopic"], "12.4 10.8 1.3": ["nerding"], "7.6 5.1 1.9": ["lightfastness"], "11.7 7.8 28.1": ["sploshing"], "6.0 17.5 14.1": ["mudballs"], "9.4 -0.7 19.2": ["winterwear"], "0.8 6.2 -0.5": ["applicative"], "-3.4 -1.3 2.3": ["dialyses"], "8.1 11.3 11.1": ["stips"], "9.7 4.5 18.6": ["chewies"], "3.7 7.5 16.9": ["jeon"], "-3.8 -3.7 0.2": ["nals"], "2.5 14.2 6.6": ["initialism"], "15.2 6.6 20.6": ["pelletizer"], "-4.3 0.5 3.0": ["singjay"], "-1.3 4.8 11.9": ["orginially"], "16.8 6.2 35.8": ["mirliton"], "1.5 16.5 25.2": ["reseeds"], "10.3 2.5 24.1": ["tabua"], "-0.5 7.5 16.4": ["researchable"], "-0.0 -0.5 -2.8": ["desktopsites"], "0.0 1.2 6.2": ["toktok"], "9.5 3.8 14.5": ["skinsuits"], "11.5 28.2 17.3": ["whimp"], "0.8 24.3 1.5": ["allie"], "14.5 5.9 15.3": ["foulard"], "11.3 4.2 39.4": ["misto"], "-1.1 10.8 7.8": ["unki"], "5.8 -3.5 8.9": ["biocomposite"], "-2.1 1.5 5.1": ["verbaled"], "4.7 7.3 34.9": ["vibriosis"], "18.7 6.5 20.3": ["orderbooks"], "15.2 14.1 25.3": ["rototillers"], "14.9 6.6 43.8": ["coley"], "-0.1 14.0 3.3": ["frome"], "11.0 -5.6 6.8": ["emalangeni"], "-5.4 -2.9 15.8": ["pedis"], "4.5 4.6 5.8": ["encephalomyelitis"], "9.9 3.5 21.9": ["insectary"], "7.3 9.3 -2.8": ["suppo"], "11.3 10.5 6.4": ["tzuoo"], "19.2 3.3 13.1": ["clads"], "9.1 5.8 3.4": ["reis"], "17.4 3.3 -0.7": ["builiding"], "28.4 4.4 16.2": ["capered"], "2.7 8.9 9.9": ["thespic"], "15.9 7.0 10.2": ["keened"], "11.5 10.5 13.4": ["cokeheads"], "-1.5 2.5 8.9": ["abhiyan"], "7.1 18.2 8.2": ["nomatter"], "6.2 13.1 6.8": ["karam"], "8.0 12.0 10.0": ["peculation"], "13.3 14.8 21.0": ["browny"], "0.3 4.0 11.7": ["jeune"], "13.6 19.5 12.5": ["muthafuckin"], "15.7 -9.1 -6.7": ["nnounced"], "9.1 -0.5 8.3": ["entrepreneural"], "20.3 15.6 30.3": ["buttonbush"], "-4.4 7.1 4.7": ["craniotomies"], "2.0 -1.3 14.7": ["arabbers"], "0.3 8.9 14.6": ["jadi"], "13.2 24.8 23.0": ["squaws"], "3.4 7.5 24.7": ["bawal"], "3.1 4.0 8.9": ["mountainbiker"], "0.6 17.5 19.3": ["coinflip"], "23.3 10.9 17.7": ["dingus"], "-0.3 10.0 20.0": ["choti"], "5.9 18.5 18.0": ["indeterminately"], "7.4 7.1 6.7": ["overbuilders"], "18.3 0.2 19.9": ["ooohed"], "17.9 9.1 8.9": ["subsidizers"], "9.1 3.9 18.0": ["cornetto"], "1.4 -9.4 2.6": ["llp"], "-7.5 3.3 8.5": ["yavusa"], "13.0 18.6 5.7": ["zombied"], "1.0 14.1 14.0": ["caucasion"], "11.6 7.1 10.5": ["zullen"], "14.0 5.7 9.2": ["pfl"], "16.0 11.8 17.8": ["megacaps"], "14.7 19.2 -7.4": ["unmistaken"], "5.1 4.5 11.8": ["achat"], "10.2 -1.8 8.6": ["unshredded"], "1.8 8.3 11.4": ["bradykinesia"], "18.0 0.6 6.6": ["percnt"], "1.0 19.8 12.5": ["lession"], "11.2 4.4 10.3": ["disneyland"], "8.4 7.8 11.7": ["madonnas"], "12.0 3.9 20.2": ["tweaky"], "16.5 4.6 11.9": ["bizz"], "8.6 1.8 37.1": ["bammy"], "8.6 3.7 34.2": ["ricing"], "3.1 0.8 6.4": ["fes"], "3.9 6.4 4.4": ["nonmarketable"], "22.1 17.3 26.2": ["scudded"], "8.1 -1.8 13.4": ["hammond"], "10.4 13.7 6.3": ["testiest"], "13.2 12.7 10.4": ["recenter"], "3.6 8.3 5.7": ["shorteners"], "0.2 6.6 13.6": ["nimo"], "7.3 22.6 6.4": ["approch"], "9.9 14.8 2.0": ["tabletoppers"], "24.3 9.9 24.6": ["fanlike"], "13.3 9.9 14.3": ["dumpyard"], "12.6 8.9 12.1": ["moonship"], "2.3 1.2 6.4": ["prgms"], "11.1 12.9 -8.9": ["responsiblefor"], "-3.4 10.5 21.7": ["korban"], "14.8 16.6 9.3": ["fuzzes"], "6.6 2.8 14.5": ["powerwashing"], "6.9 -0.8 4.8": ["emedia"], "5.1 18.7 11.1": ["anythign"], "-2.8 9.9 5.1": ["independants"], "7.2 10.3 4.4": ["attys"], "1.2 6.4 10.2": ["avarage"], "14.4 29.9 23.3": ["reptilians"], "15.8 8.4 23.0": ["elderflowers"], "3.9 11.9 9.1": ["fadeway"], "11.0 12.4 10.6": ["slicksters"], "23.4 16.1 20.6": ["doorknocker"], "0.5 14.1 5.9": ["bouncebacks"], "2.1 13.5 5.7": ["affiliative"], "7.2 13.0 9.2": ["hadto"], "9.8 9.0 7.8": ["freewheeled"], "4.5 16.6 4.1": ["intertextual"], "4.8 5.2 8.3": ["trouve"], "0.1 21.3 16.8": ["beirut"], "2.7 18.7 3.7": ["nanostructuring"], "19.1 16.2 3.0": ["unremovable"], "5.7 4.7 11.5": ["decalcification"], "2.8 -2.4 4.9": ["sportsgrounds"], "-7.8 11.0 1.2": ["sefer"], "15.5 5.3 13.6": ["bedrail"], "-2.3 4.7 0.9": ["metamodel"], "-2.3 11.6 5.2": ["multicam"], "11.2 7.6 12.5": ["suvs"], "17.1 25.0 8.1": ["rozzers"], "11.1 7.5 20.1": ["nabes"], "2.7 12.9 3.0": ["idiotype"], "-2.7 0.7 9.7": ["rees"], "10.7 21.3 15.1": ["uglification"], "13.5 7.3 10.5": ["reflated"], "-0.4 -0.9 17.7": ["verdelho"], "9.0 -5.6 11.3": ["aparthotel"], "-1.4 -6.0 -0.3": ["posponed"], "1.2 7.7 4.0": ["plasticizing"], "5.8 5.8 27.1": ["bulgar"], "1.9 20.0 6.2": ["temporariness"], "9.1 10.1 14.8": ["julian"], "4.2 14.6 16.1": ["corpsing"], "11.5 6.6 21.0": ["slurpees"], "-2.6 4.9 8.4": ["merong"], "7.3 5.0 -2.1": ["konnte"], "0.8 10.4 6.8": ["formulaically"], "3.6 7.7 15.5": ["gawa"], "-2.9 3.7 4.3": ["elem"], "1.1 24.4 10.9": ["quirkyalone"], "17.0 10.7 -0.7": ["spindoctor"], "-2.6 12.2 0.6": ["dispensationalism"], "9.0 9.8 3.7": ["monosaccharide"], "10.3 1.4 39.1": ["scaloppine"], "11.3 13.1 22.4": ["sapien"], "19.3 10.7 21.4": ["tamagotchi"], "7.0 -4.2 -2.8": ["submeters"], "6.0 12.4 15.4": ["stiller"], "5.4 26.4 7.7": ["justifier"], "-9.4 23.7 7.0": ["soever"], "2.2 4.9 7.7": ["trichiasis"], "10.8 9.4 13.8": ["pixelization"], "13.9 -7.3 12.9": ["ariary"], "10.3 21.8 9.3": ["inconsequentiality"], "8.9 22.7 22.2": ["foxhunt"], "-4.1 0.5 1.4": ["polysomnographic"], "4.8 17.7 -0.2": ["begetter"], "6.9 12.4 4.8": ["browseable"], "25.8 -1.1 17.7": ["waltzers"], "9.2 0.8 9.4": ["nonpoints"], "2.9 10.8 16.1": ["nicki"], "12.7 -0.5 5.0": ["wooga"], "4.5 11.5 16.1": ["delayers"], "2.7 11.1 8.5": ["glycolipids"], "8.5 8.6 25.8": ["argonauts"], "5.9 -4.7 9.9": ["hartford"], "-0.9 4.3 10.0": ["poinst"], "-1.3 14.7 10.6": ["hyperthermic"], "10.7 16.8 8.0": ["unleveled"], "1.2 1.7 -0.7": ["bez"], "5.9 -6.7 -0.3": ["uro"], "9.9 16.9 8.3": ["quicly"], "-0.1 4.8 14.5": ["ghagra"], "-1.9 15.5 4.2": ["thesituation"], "0.4 14.5 9.6": ["photostat"], "-5.8 15.1 10.8": ["chronos"], "4.4 10.0 9.7": ["darkfield"], "15.5 -2.6 6.1": ["fashionwear"], "11.0 17.2 9.9": ["cauterizes"], "7.6 17.3 9.3": ["clunkiest"], "-8.3 20.4 0.4": ["religeous"], "3.5 7.6 -3.6": ["videoscope"], "-3.5 7.9 4.7": ["edemas"], "13.8 2.8 7.3": ["sla"], "-1.1 1.5 7.0": ["situationer"], "-2.7 10.2 -3.3": ["destooled"], "8.2 10.0 5.6": ["nopooh"], "1.3 8.8 5.9": ["fightcard"], "4.8 8.5 16.0": ["booklover", "kalye"], "1.5 3.7 2.1": ["inculding"], "2.9 8.7 10.9": ["stoppped"], "5.3 10.4 0.4": ["unilluminating"], "9.1 3.3 20.8": ["saltpans"], "15.1 24.9 13.6": ["poltroons"], "3.7 -4.7 10.4": ["roedd"], "11.3 10.4 4.9": ["beed"], "6.8 1.7 11.7": ["viejo"], "10.3 9.3 32.1": ["bullfinch"], "6.7 17.2 7.8": ["lexicographical"], "14.0 11.7 12.4": ["nursemaids"], "-0.8 3.7 10.8": ["schoolin"], "10.8 19.4 8.1": ["immersiveness"], "5.4 11.2 8.3": ["baraatis"], "0.0 5.4 8.5": ["peaksaver"], "19.2 6.5 11.0": ["junkware"], "3.2 12.0 8.7": ["labyrinthitis"], "23.5 12.8 10.6": ["scrofulous"], "2.5 -1.3 27.5": ["supramax"], "14.3 5.8 8.3": ["rehanging"], "8.9 19.7 17.9": ["groundswells"], "1.8 -0.5 18.1": ["yat"], "-1.6 18.4 11.0": ["womanist"], "10.5 1.5 13.4": ["farwell"], "-1.7 7.3 6.7": ["sisterhoods"], "8.0 10.4 10.5": ["sidecurls"], "17.3 15.9 15.2": ["shagadelic"], "8.5 2.4 10.1": ["flosser"], "4.9 17.6 10.0": ["lexis"], "14.0 2.7 10.7": ["rythms"], "11.4 27.5 7.4": ["hellbound"], "13.0 9.9 11.4": ["realz"], "8.5 2.6 -2.0": ["neuromodulators"], "2.7 15.1 3.8": ["offsiders"], "5.5 11.2 11.0": ["bullbars", "matan"], "12.0 16.3 39.5": ["redtails"], "8.6 27.2 2.6": ["denouncers"], "-1.7 7.7 -2.8": ["spokseman"], "-9.6 6.5 8.0": ["interjurisdictional"], "-8.6 12.3 -0.4": ["deradicalization"], "6.5 12.1 12.4": ["mineralize"], "-6.5 4.2 13.6": ["germaneness"], "5.7 12.6 12.8": ["ddesy"], "15.8 6.3 20.9": ["chippery"], "13.6 22.5 8.8": ["eradicator"], "-0.9 6.8 -0.9": ["farily"], "2.0 14.0 12.2": ["scrimage"], "9.3 10.4 22.7": ["canoer"], "6.1 12.9 9.4": ["sallah"], "9.1 14.6 5.9": ["spindoctors"], "13.0 18.4 12.4": ["whenit"], "2.5 12.1 7.3": ["palaeochannels"], "9.9 9.0 5.7": ["totalization"], "7.7 7.6 6.8": ["grupero"], "5.3 10.1 16.4": ["chunni"], "-2.8 6.7 9.9": ["autoregulation"], "9.0 7.7 7.0": ["microstructured"], "18.9 27.1 10.9": ["peashooters"], "-4.0 0.8 1.9": ["overcollateralisation"], "-3.0 12.7 2.9": ["eveidence"], "6.8 13.5 7.3": ["hyundai"], "-6.4 12.0 4.9": ["tiime"], "11.4 8.9 10.6": ["ampersands"], "14.0 8.0 10.9": ["crowbarred"], "0.3 23.6 10.3": ["onload"], "0.9 13.7 20.7": ["flexitarians"], "15.7 4.2 17.0": ["sackloads"], "7.0 -2.1 4.0": ["editorships"], "2.9 8.5 1.5": ["witt"], "13.9 3.6 2.8": ["piccies"], "10.0 18.4 11.1": ["opensider"], "11.5 16.6 22.7": ["sleepyhead"], "6.7 24.1 5.7": ["repsonsibility"], "12.0 24.4 6.4": ["stonethrowers"], "0.8 12.8 3.4": ["decissions"], "8.6 18.3 11.2": ["crysis"], "13.1 10.9 13.3": ["modishly"], "22.2 12.9 19.6": ["cherrypicker"], "12.4 5.8 7.0": ["wellwisher"], "4.0 3.0 7.9": ["seasonending"], "5.3 10.3 1.1": ["infrastructurally"], "-12.5 -1.3 4.7": ["preop"], "15.9 14.2 6.1": ["squanderers"], "7.1 7.9 18.9": ["lampwork"], "13.0 1.1 12.0": ["cheh"], "11.1 -1.4 4.6": ["sxsw"], "9.2 6.3 0.7": ["advents"], "8.4 -1.5 -2.8": ["seting"], "21.5 10.3 16.1": ["gammy"], "6.0 2.4 6.9": ["multihospital"], "7.6 10.5 9.3": ["biohazardous"], "3.6 1.2 12.6": ["dreampharmaceuticals"], "20.0 11.8 13.6": ["simoleons"], "16.0 9.9 33.0": ["kebob"], "10.0 0.1 21.4": ["fixatives"], "-0.8 0.3 13.5": ["edematous"], "1.9 3.0 11.1": ["drwy"], "-0.7 4.8 12.3": ["desisyon"], "8.3 3.5 6.6": ["hydromassage"], "2.1 2.4 4.6": ["heterocyclic"], "4.6 15.8 23.3": ["coursers"], "6.0 6.1 11.1": ["unpegging"], "8.1 10.1 6.5": ["megafights"], "7.7 15.1 3.8": ["legate"], "10.7 13.6 12.8": ["passwd"], "16.9 2.9 4.4": ["anational"], "8.7 -2.0 21.8": ["plumy"], "14.7 24.4 3.2": ["bullshitters"], "21.2 4.3 17.6": ["burled"], "-1.3 -1.4 10.6": ["bednights"], "11.8 11.3 5.7": ["loverman"], "17.8 3.8 6.2": ["mpegs"], "4.0 9.3 16.1": ["panalo"], "-0.6 15.0 7.3": ["groupmates"], "0.4 -2.1 13.0": ["kash"], "8.3 7.8 38.3": ["gnudi"], "6.8 21.1 6.1": ["wayyyyy"], "6.3 8.1 8.3": ["extrordinary"], "14.2 5.3 28.6": ["tamarindo"], "-5.6 -1.1 -3.8": ["stp"], "11.5 9.3 7.9": ["slivovitz"], "6.0 3.0 5.1": ["deannex"], "-0.0 15.2 13.1": ["recompute"], "2.3 8.3 9.8": ["miranda"], "-4.0 20.4 9.3": ["doubleness"], "6.1 9.4 18.9": ["hiim"], "-2.8 13.6 -1.1": ["saught"], "20.6 6.9 20.8": ["matelasse"], "17.3 36.4 16.4": ["necromantic"], "10.5 15.5 23.8": ["hibernaculum"], "10.1 16.6 6.0": ["secruity"], "4.9 4.5 7.2": ["fuchsite"], "2.6 3.1 9.8": ["erly"], "17.2 15.2 10.5": ["gba"], "4.2 7.8 17.3": ["milds"], "6.3 8.1 15.7": ["slenderize"], "-2.6 22.9 10.6": ["pupose"], "5.5 5.8 13.5": ["uninsureds"], "16.8 11.7 16.0": ["gack"], "6.0 11.3 16.2": ["vanhu"], "-4.1 -3.3 -3.6": ["appts"], "14.3 19.4 6.9": ["straightjacketed"], "9.1 7.7 -5.1": ["othercountries"], "9.4 2.4 8.3": ["hilltown"], "9.7 9.0 3.9": ["dpg"], "-1.5 7.3 0.5": ["airparks"], "3.3 11.8 8.4": ["creepage"], "-3.0 9.1 1.0": ["confabulating"], "7.5 -2.8 -13.5": ["spol"], "15.9 5.3 30.7": ["kalamata"], "-1.3 -2.3 0.3": ["norethindrone"], "15.5 3.6 3.2": ["airmailing"], "8.0 5.1 21.0": ["ammoniac"], "5.1 23.1 7.7": ["awam"], "-3.0 20.0 3.3": ["agressiveness"], "-3.1 12.7 13.4": ["exsanguination"], "6.8 10.9 12.9": ["qin"], "13.0 15.4 12.7": ["washerwomen"], "11.1 7.8 21.5": ["hydroacoustic"], "0.2 28.0 9.2": ["neshama"], "-0.9 1.9 5.7": ["thrombopoietin"], "-8.0 8.8 7.8": ["backoff"], "20.8 9.1 17.9": ["gambols"], "2.0 0.1 5.1": ["promotores"], "8.4 6.8 4.2": ["lithotripters"], "17.2 23.9 11.1": ["blunderers"], "5.9 10.1 21.4": ["transhipments"], "6.2 9.1 13.7": ["wichita"], "4.2 -4.1 2.8": ["imputs"], "5.9 12.0 24.2": ["lightish"], "12.8 7.4 6.8": ["overproduces"], "11.6 14.8 15.5": ["fata"], "7.9 12.4 3.6": ["exopolitics"], "7.9 14.8 12.8": ["movesets"], "6.4 9.3 7.4": ["tradtion"], "5.6 16.9 13.2": ["incommunicative"], "12.8 20.0 3.4": ["publicness"], "7.9 -0.5 6.0": ["cfc"], "0.5 6.3 1.8": ["nanofluids"], "15.5 9.5 15.1": ["scantiest"], "0.6 25.1 7.9": ["puttar"], "-3.5 15.5 6.8": ["hyperacusis"], "9.9 11.2 5.0": ["timepass"], "-0.8 33.3 5.4": ["soilders"], "18.0 11.9 11.4": ["worldbeaters"], "6.0 18.8 7.2": ["gamercard"], "5.5 6.7 11.7": ["dedifferentiation"], "6.2 0.0 7.6": ["gastroscope"], "8.6 6.4 11.1": ["noncyclical"], "7.3 11.8 9.0": ["bombay"], "12.7 9.0 2.4": ["arsine"], "15.4 1.0 0.1": ["chellomedia"], "10.1 17.4 -0.4": ["foulplay"], "1.3 11.6 12.4": ["seconditis"], "11.8 1.4 6.5": ["prodcuts"], "-5.5 20.1 -2.4": ["dissatisfy"], "-4.3 7.3 9.9": ["debriding"], "6.8 0.4 7.7": ["wakaf"], "8.6 11.0 6.8": ["circumflex"], "15.8 12.3 12.0": ["ungreen"], "-3.2 4.2 14.8": ["raspiness"], "3.0 7.5 7.5": ["fourh"], "16.0 13.3 43.0": ["fishermens"], "-5.4 -2.4 9.3": ["recyclates"], "1.5 3.8 -9.9": ["scrutinizer"], "18.2 1.2 7.8": ["superlawyer"], "15.1 12.6 15.6": ["silvertails"], "0.1 8.4 6.4": ["ij"], "16.6 7.7 21.1": ["argan"], "14.8 20.2 17.2": ["copulatory"], "-5.0 10.1 4.0": ["endemicity"], "-0.2 -3.2 15.5": ["blowdry"], "13.1 10.0 8.7": ["breakcore"], "7.3 7.6 -5.4": ["succ"], "22.2 3.1 6.5": ["megadevelopment"], "6.0 13.1 -10.4": ["ambassdor"], "-9.4 11.6 -5.2": ["ensive"], "8.9 12.5 6.0": ["insur"], "19.9 24.2 13.6": ["stygian"], "14.5 9.4 15.2": ["parallelograms"], "-1.5 10.9 1.2": ["keept"], "5.9 3.2 33.4": ["portabellas"], "10.7 13.8 16.2": ["smidgens"], "-1.3 2.5 11.5": ["previos", "haal"], "11.5 19.4 25.0": ["sabots"], "1.0 16.8 12.4": ["demurrals"], "15.1 8.0 21.4": ["oatcake"], "9.8 11.6 13.4": ["trippiness"], "10.7 10.4 17.4": ["itabirite"], "12.7 14.5 20.2": ["pshaw"], "2.4 5.0 12.3": ["mmc"], "4.8 5.2 4.2": ["mbbl"], "4.5 6.9 18.5": ["sharbat"], "7.4 14.0 32.3": ["polynya"], "18.0 11.6 7.4": ["amorphously"], "0.3 2.1 -8.4": ["respresentative"], "2.0 10.3 6.6": ["neuroligins"], "0.5 5.9 17.0": ["jojo"], "1.7 9.0 6.7": ["sociably"], "-2.6 11.9 6.2": ["zaroor"], "4.9 31.5 3.0": ["destablizing"], "-0.6 9.3 6.0": ["packetization"], "12.8 -5.0 18.8": ["sapele"], "13.5 11.4 11.8": ["wraped"], "9.9 -12.4 8.7": ["thwe"], "27.9 3.5 15.5": ["bings"], "12.6 14.8 22.6": ["poopers"], "3.8 10.7 4.2": ["semiquantitative"], "2.9 -5.4 20.9": ["ecomaine"], "19.2 5.6 12.9": ["belen"], "-4.7 5.5 4.7": ["financee"], "10.3 12.7 17.8": ["chirrups"], "-3.5 17.3 -1.8": ["plenipotentiaries"], "3.0 6.2 19.1": ["cfl"], "8.3 1.8 8.8": ["catalan"], "4.9 20.6 3.4": ["khalifa"], "6.7 13.4 12.2": ["garimpeiro"], "-0.9 -4.7 2.4": ["aromatherapists"], "6.9 1.1 1.1": ["rmetzler"], "6.8 13.0 15.4": ["washdowns"], "9.2 -2.4 6.9": ["booksale"], "5.7 13.9 7.1": ["evel"], "-1.0 3.7 8.6": ["exomes"], "0.3 24.6 7.7": ["overcomer"], "11.7 10.2 6.5": ["scandinavian"], "7.6 1.8 -1.0": ["veepee"], "13.7 19.2 1.9": ["crackable"], "16.5 2.6 19.1": ["pegboards"], "11.9 17.9 -2.3": ["encouter"], "15.3 -11.3 5.1": ["minibond"], "8.4 10.3 45.5": ["lugworm"], "7.2 3.5 1.4": ["memorium"], "10.2 13.3 16.0": ["ragtops"], "-3.8 1.8 12.8": ["ragam"], "19.7 0.3 31.1": ["tuille"], "18.0 10.8 8.9": ["dreamliner"], "1.9 2.6 4.3": ["dopo"], "6.6 7.1 6.2": ["launchd"], "8.3 27.0 9.7": ["distroy"], "0.8 -3.0 12.4": ["unalloted"], "-4.0 -2.1 2.1": ["videostream"], "0.2 6.0 2.9": ["loxapine"], "18.1 0.8 37.0": ["brocolli"], "-1.0 6.9 1.1": ["angiographically"], "1.3 21.5 13.2": ["solipsist"], "3.3 6.6 11.1": ["chares"], "4.5 8.3 11.0": ["drawbars"], "1.1 18.3 11.5": ["uski"], "4.5 -0.8 5.7": ["aminocandin"], "1.3 24.2 8.8": ["karuna"], "6.1 11.4 24.5": ["hasher"], "15.0 2.3 30.4": ["bacony"], "21.9 18.6 39.7": ["hornworm"], "-0.9 11.1 10.7": ["linedrive"], "0.9 8.2 2.0": ["sason"], "3.8 -7.3 5.5": ["springbreak"], "12.0 23.5 4.2": ["tyrannised"], "4.6 3.0 11.5": ["tila"], "1.7 1.9 8.1": ["greylisting"], "1.6 1.8 6.3": ["accompained"], "4.1 0.9 6.4": ["compat"], "2.2 19.1 3.7": ["cantoned"], "9.6 6.6 12.0": ["coolstores"], "14.9 1.4 6.4": ["hedgefund"], "-9.9 0.8 4.9": ["senatorship"], "4.8 21.4 2.6": ["rying"], "-2.5 2.4 10.5": ["benef"], "12.8 8.0 11.2": ["headbox"], "4.9 3.2 18.6": ["pourings"], "-4.6 18.6 4.4": ["escapeways"], "5.9 24.8 9.4": ["badman"], "0.2 3.4 6.5": ["cefotaxime"], "4.5 11.6 14.0": ["katcha"], "4.0 7.2 26.0": ["pamela"], "-0.4 -1.8 4.2": ["matchers"], "7.7 14.5 18.2": ["untwisting"], "9.6 5.9 40.7": ["mycobacteriosis"], "6.1 26.1 5.0": ["mahajot"], "-2.0 12.4 4.1": ["revictimize"], "10.1 27.4 25.3": ["nematocysts"], "4.7 6.2 7.9": ["humidistat"], "-1.2 12.6 16.0": ["rhizosphere"], "1.7 7.1 1.2": ["haemostatic"], "13.4 5.1 7.1": ["maken"], "3.4 15.4 8.0": ["coreceptor"], "11.9 8.5 29.4": ["amaretti"], "1.2 7.5 11.8": ["coblation"], "10.5 9.9 9.0": ["commutator"], "17.6 8.2 15.1": ["stetsons"], "5.9 13.4 11.0": ["agroecological"], "-2.7 10.5 12.8": ["infiltrative"], "5.7 -4.4 9.4": ["remining"], "-2.0 9.3 7.6": ["bonum"], "10.1 8.2 26.3": ["dosai"], "1.1 3.0 12.0": ["blong"], "3.9 6.5 6.4": ["otamixaban"], "8.5 19.7 3.6": ["diegetic"], "6.5 10.8 -3.1": ["leaderin"], "4.0 -1.4 8.3": ["playschools"], "4.6 9.1 14.3": ["perambulate"], "-1.3 3.0 -2.2": ["substitutional"], "14.7 6.5 21.4": ["coffeecakes"], "5.5 5.2 3.4": ["shoppette"], "0.7 3.7 5.1": ["apos"], "23.3 16.0 36.8": ["pollywogs"], "7.1 3.4 11.7": ["treasurable"], "14.0 16.5 7.0": ["fuddy"], "9.0 15.0 2.3": ["chessmaster"], "2.0 25.3 12.0": ["definitionally"], "5.0 6.1 7.5": ["fanstastic"], "12.9 10.6 12.8": ["favoritest"], "6.7 8.9 2.0": ["elmination"], "6.3 20.3 8.0": ["gameplaying"], "-2.4 -5.8 5.1": ["playschemes"], "6.0 0.9 5.8": ["underdeclaration"], "17.6 0.9 14.2": ["mico"], "13.4 14.1 30.5": ["yaupon"], "10.8 2.4 7.7": ["basebal"], "8.1 6.6 3.2": ["dealwith"], "2.2 11.1 3.5": ["compell"], "9.3 3.9 44.3": ["bourguignon"], "22.8 11.0 18.5": ["conehead"], "4.4 6.8 6.5": ["toexpand"], "17.1 22.4 36.6": ["brushpile"], "-1.0 6.9 -2.7": ["committs"], "16.2 21.3 10.4": ["yawp"], "15.4 3.9 9.1": ["compacter"], "10.9 -7.6 6.0": ["bdp"], "3.7 8.3 8.9": ["relogging"], "12.1 7.2 19.1": ["fortuna"], "-0.2 5.4 11.4": ["senatoriables"], "1.1 -0.2 13.4": ["compris"], "-1.6 12.0 10.5": ["pogi"], "10.7 -1.4 6.3": ["halfdozen"], "3.9 1.0 8.6": ["gelcaps"], "-2.5 0.2 7.2": ["homograft"], "8.4 3.8 11.1": ["dorp"], "8.0 -5.4 3.1": ["announcments"], "5.3 4.0 13.8": ["orts"], "4.3 23.1 12.2": ["ringingly"], "9.1 2.9 6.2": ["occluder"], "14.3 5.4 8.2": ["kigango"], "8.2 13.3 9.4": ["forgettably"], "4.6 8.6 12.2": ["imovie"], "15.7 10.9 10.2": ["snootiest"], "26.7 16.1 17.4": ["spadeful"], "19.5 10.6 18.0": ["jandal"], "10.7 -1.7 4.5": ["roofdeck"], "6.3 10.6 20.2": ["multigene"], "6.7 1.6 19.7": ["wildwater"], "16.7 5.9 13.1": ["hogans"], "13.3 -3.3 2.9": ["ibuyeco"], "7.6 0.7 8.8": ["cheg"], "9.0 3.6 7.5": ["tractorcade"], "10.1 10.0 11.0": ["wettable"], "1.4 4.1 1.9": ["autospy"], "22.0 9.8 36.5": ["porkchop"], "8.1 0.0 12.1": ["twnhse"], "8.1 9.9 11.0": ["lollygagged"], "0.6 24.2 6.1": ["protaganist"], "12.2 5.6 11.1": ["exhalative"], "7.7 11.8 19.0": ["saprolitic"], "0.0 -3.3 -3.1": ["assis"], "7.9 13.6 20.7": ["vacationland"], "7.8 6.7 15.6": ["palang"], "16.1 11.7 34.7": ["hamiltoni"], "1.1 8.0 11.8": ["crimen"], "3.0 10.2 0.8": ["froms"], "23.7 19.2 12.3": ["superdog"], "10.9 4.8 32.4": ["butterhead"], "-4.6 7.8 5.7": ["haematologic"], "5.4 -3.5 10.6": ["nard"], "1.2 1.1 9.3": ["replatting"], "19.9 7.0 1.6": ["revolutionalize"], "10.1 14.7 13.8": ["pano"], "3.4 6.5 10.0": ["rhodamine"], "9.4 6.1 4.5": ["aby"], "2.6 -1.8 20.7": ["greenroof"], "1.1 18.8 3.6": ["vedas"], "1.7 0.1 7.6": ["brivaracetam"], "-8.3 19.1 -2.7": ["inspirers"], "0.4 9.7 7.0": ["extrahepatic"], "-3.6 -2.9 2.6": ["honourarium"], "6.5 15.9 7.4": ["underinflation"], "4.9 5.9 10.0": ["akes"], "14.6 17.3 7.4": ["demagnetize"], "2.1 5.0 7.8": ["projectability"], "11.3 5.0 4.2": ["heterojunction"], "16.5 3.3 2.6": ["toursim"], "5.0 1.9 -0.7": ["nanocatalyst"], "6.8 7.7 13.0": ["andhad"], "-2.2 7.3 7.9": ["cpc"], "3.1 9.4 7.6": ["webber"], "3.6 1.6 8.3": ["hts"], "0.5 9.4 -1.7": ["exegeses"], "6.3 4.8 10.2": ["hanson"], "4.3 20.8 10.6": ["traceur"], "4.5 -0.7 11.6": ["speel"], "11.3 10.0 15.6": ["thaneb", "rugging"], "12.2 9.4 14.3": ["livewires"], "-2.6 3.3 -12.8": ["nally"], "15.2 7.8 0.1": ["theformer"], "11.4 0.7 49.5": ["hammour"], "-6.8 37.4 4.3": ["deterrable"], "-3.4 5.4 24.8": ["amontillado"], "3.1 7.5 5.1": ["hyperpolarization"], "11.1 19.8 14.7": ["woodline"], "19.8 3.7 15.0": ["partyware"], "3.9 6.9 -7.9": ["organsation"], "-0.6 8.5 10.1": ["teeoff"], "11.5 5.7 19.2": ["pilsener"], "-7.6 9.2 -4.1": ["promotee"], "20.7 10.5 12.8": ["bricklike"], "-4.2 4.8 10.7": ["concelebration"], "7.4 8.7 16.0": ["redtape"], "5.4 -1.0 -0.0": ["datacast"], "-3.5 22.4 6.7": ["overfamiliarity"], "-0.3 10.5 28.9": ["nonhunting"], "10.7 2.6 16.6": ["herwin"], "7.5 9.6 12.1": ["nfc"], "9.7 17.9 24.2": ["offish"], "11.9 -0.2 5.1": ["purchse"], "3.6 10.9 7.4": ["gluteals"], "4.6 14.6 7.4": ["vociferousness"], "1.9 7.0 15.4": ["spermidine"], "4.5 15.9 4.1": ["soreheads"], "9.6 36.9 14.7": ["protoss"], "0.5 5.7 2.4": ["efiling"], "5.4 13.7 13.7": ["gibbs"], "-2.5 11.2 -5.1": ["withn"], "5.8 2.2 -1.8": ["kickstarter"], "8.0 14.9 4.2": ["samaritans"], "-6.2 -8.3 6.8": ["nne"], "-0.1 5.2 11.0": ["bovis"], "8.5 2.9 10.8": ["lifesavings"], "16.9 6.5 30.3": ["crunchiest"], "-7.9 5.0 5.3": ["nonparent"], "19.0 3.2 34.7": ["cazuela"], "6.6 11.5 6.9": ["suraj"], "1.2 8.7 11.8": ["coplanarity"], "8.7 4.3 28.0": ["pua"], "-12.6 10.6 4.0": ["recidivate"], "17.2 10.2 19.9": ["spitz"], "4.5 16.1 10.9": ["privelage"], "4.8 13.7 11.0": ["unexpressive"], "5.5 7.3 4.6": ["unregister"], "13.8 3.7 15.7": ["behaviourists"], "16.0 5.8 14.6": ["stereographs"], "-0.8 -2.4 5.8": ["ehl"], "-8.9 -0.2 -8.7": ["visisted"], "-4.9 13.4 3.1": ["uncooperativeness"], "4.3 12.3 17.4": ["kalou"], "11.8 2.7 29.7": ["tava"], "-3.1 -0.3 11.2": ["onehour"], "15.6 -1.3 12.6": ["preneur"], "8.0 19.6 5.6": ["determinists"], "14.8 2.9 11.5": ["meteorologic"], "13.9 19.2 11.5": ["roughhoused"], "7.4 -0.7 -0.9": ["resarch"], "10.9 2.9 16.3": ["draff"], "-9.0 6.8 -0.9": ["arteriography"], "14.8 13.7 14.4": ["leathering"], "-0.2 10.8 10.5": ["raags"], "12.3 15.5 4.3": ["backchannels"], "-0.5 5.4 -2.7": ["protec"], "-4.7 28.7 1.9": ["casulaties"], "9.5 0.5 14.1": ["twostory"], "18.7 1.8 6.3": ["ofproducts"], "2.9 14.6 2.0": ["detainess"], "9.5 15.4 13.1": ["notrump"], "10.8 11.0 12.5": ["outblocking"], "11.4 8.9 4.7": ["ultrasafe"], "-2.2 24.9 6.0": ["reachback"], "7.2 7.0 27.9": ["modaks"], "22.5 19.1 15.2": ["catoms"], "14.2 2.4 13.4": ["gristmills"], "15.8 9.7 16.6": ["serpentines"], "8.2 13.1 9.8": ["elp"], "7.7 31.6 10.5": ["determinately"], "1.6 -5.8 13.3": ["finaled"], "8.2 17.9 5.2": ["intellectualising"], "4.1 16.9 12.8": ["xylan"], "-0.3 15.3 7.1": ["nanolaser"], "6.8 20.7 4.4": ["putsches"], "5.4 -0.9 14.3": ["microalgal"], "16.8 6.7 14.0": ["tugger"], "5.9 -0.6 -7.2": ["outsted"], "2.1 -0.9 11.9": ["syncrude"], "6.7 17.5 7.6": ["propitiously"], "0.4 -1.3 3.2": ["crossvision"], "14.6 10.9 19.5": ["cashola"], "-3.1 1.4 8.2": ["mehfil"], "19.6 2.2 20.6": ["parols"], "10.6 -2.0 13.5": ["onomics"], "-17.9 -2.8 -3.3": ["expalined"], "4.4 6.6 7.6": ["sophie"], "6.5 -13.1 3.7": ["ofmore"], "14.2 16.7 8.5": ["radiosondes"], "9.5 6.2 27.0": ["yellowhammers"], "9.4 16.6 20.3": ["nuf"], "1.3 9.6 9.6": ["cardinality"], "17.2 11.7 15.0": ["ooohhh"], "7.3 17.7 10.8": ["speleologists"], "7.0 6.2 11.8": ["threadwork"], "6.9 6.5 4.6": ["multiphonics"], "10.4 10.3 13.5": ["unprintables"], "8.7 7.9 8.6": ["homeworker"], "10.4 3.6 21.5": ["cocina"], "1.8 4.9 18.3": ["yeung"], "-2.7 4.2 18.2": ["snowmelts"], "4.2 -6.4 -5.0": ["colaboration"], "3.4 17.0 6.4": ["comelec"], "7.3 3.6 9.0": ["gdi"], "16.8 19.3 11.3": ["guttersnipes"], "8.8 10.1 9.7": ["spazzes"], "-8.5 3.9 13.2": ["mabait"], "7.4 0.8 9.4": ["pmpm"], "4.9 9.2 -0.8": ["pretexted"], "5.5 7.9 8.2": ["retured"], "15.9 12.9 26.5": ["jowled"], "25.6 10.2 15.5": ["cagelike"], "17.7 25.7 12.7": ["supergirl"], "6.1 21.0 4.1": ["cyberstalkers"], "-5.3 15.6 7.4": ["midrashic"], "-4.0 35.3 -5.1": ["shahadat"], "-9.1 9.3 0.1": ["involement"], "3.8 3.4 9.0": ["accessiblity"], "-1.9 7.2 8.6": ["quantitive"], "9.2 8.2 28.6": ["microplane"], "6.4 10.4 14.3": ["importa"], "4.8 4.1 5.0": ["hydrolyzing"], "6.8 3.4 6.0": ["deskew"], "14.0 -2.6 -0.9": ["laiden"], "16.5 16.0 5.7": ["undraped"], "-1.1 10.4 8.0": ["pemphigoid"], "4.5 22.0 17.7": ["completionist"], "5.1 14.3 11.3": ["chroot"], "5.6 15.6 4.2": ["panegyrics"], "6.2 20.3 9.9": ["pipebombs"], "-1.3 4.7 11.2": ["ofc"], "8.6 7.3 11.2": ["stabalise"], "13.1 12.8 -3.4": ["anaylst"], "24.6 15.2 9.3": ["ascender"], "3.9 7.7 7.6": ["coastie"], "5.8 16.2 8.4": ["besought"], "0.4 3.1 0.0": ["polyomavirus"], "5.5 13.0 9.7": ["thematch"], "1.5 25.8 0.6": ["villifying"], "6.3 7.6 11.8": ["diorites"], "8.8 22.3 24.1": ["hyperreality"], "0.3 3.7 9.1": ["reapproach"], "-4.2 -2.0 6.1": ["revoted"], "10.9 -3.7 9.8": ["cesta"], "4.5 17.6 4.2": ["chessplayers"], "7.3 10.3 6.8": ["habenula"], "22.1 13.3 29.1": ["oinker"], "2.6 5.5 18.9": ["hypersaline"], "19.2 15.8 19.4": ["kettledrums"], "16.8 8.6 -1.7": ["astronautical"], "16.1 2.2 11.9": ["pelletising"], "12.9 -5.3 21.7": ["greensand"], "10.7 5.8 15.3": ["ginkgos"], "-0.0 17.6 4.2": ["jawab"], "7.2 3.9 17.7": ["hybridizations"], "11.6 18.3 9.3": ["ikee"], "9.8 10.6 11.1": ["fornicated"], "22.9 11.8 37.9": ["waxies"], "2.3 1.5 12.7": ["gwasanaeth"], "8.7 9.4 4.7": ["ratherthan"], "10.7 8.6 20.3": ["norfolk"], "6.5 11.3 8.7": ["argv"], "0.3 14.4 6.2": ["beamingly"], "13.3 13.4 21.2": ["skulling"], "-3.0 11.6 -3.0": ["tabloidization"], "-6.1 2.9 0.5": ["captioners"], "5.8 0.6 4.7": ["lookng"], "-0.4 9.6 12.5": ["noncriminals"], "10.0 1.0 8.9": ["ekiden"], "6.3 0.9 1.9": ["bds"], "-0.0 0.4 13.5": ["aml"], "7.7 11.8 9.9": ["spillet"], "7.8 17.4 2.6": ["surpress"], "7.0 -3.7 6.9": ["outrode"], "18.1 10.3 13.0": ["starrier"], "3.5 -6.8 20.5": ["koy"], "-5.4 2.5 4.2": ["viremic"], "4.5 8.3 12.9": ["hardluck"], "15.2 25.7 6.0": ["unbreached"], "11.9 6.6 14.1": ["miscellanea"], "-4.0 21.4 7.2": ["tolerence"], "12.6 16.9 14.2": ["blogland"], "9.3 1.2 14.9": ["namkeens"], "8.9 15.2 9.8": ["tailboom"], "1.6 10.4 19.1": ["skijorers"], "11.9 16.4 27.4": ["hornless"], "2.6 11.3 7.7": ["happpened"], "3.0 15.3 12.4": ["palladin"], "9.2 3.2 11.8": ["pousadas"], "19.8 10.7 18.1": ["rainbowed"], "5.7 17.4 -2.3": ["granter"], "11.2 7.2 11.1": ["unscrambles"], "3.3 2.0 11.1": ["ospital"], "5.2 7.2 23.8": ["smilax"], "12.8 2.4 30.9": ["rockmelon"], "20.6 15.2 31.4": ["robustus"], "9.0 21.6 15.7": ["uncrewed"], "10.8 17.2 2.4": ["flimflammed"], "13.2 2.7 19.6": ["crewboat"], "2.3 18.4 16.9": ["weedicides"], "6.2 16.2 12.9": ["hungriness"], "-5.6 14.8 13.7": ["thsoe"], "3.7 -5.1 10.4": ["mpa"], "8.3 5.6 18.9": ["macrophylla"], "-0.5 -0.9 16.0": ["extr"], "-3.7 6.7 5.1": ["trs"], "12.3 12.9 11.4": ["nanoantenna"], "-1.6 33.7 1.6": ["ambuscades"], "1.3 16.0 15.1": ["swiftwater"], "-0.4 4.8 5.3": ["eventfully"], "21.8 8.6 18.0": ["kettledrum"], "7.5 22.6 7.8": ["stricking"], "11.3 12.7 7.2": ["servive"], "6.9 17.4 3.3": ["metanoia"], "-1.6 9.5 19.8": ["nangyayari"], "17.6 16.8 22.2": ["shoosh"], "2.1 17.7 27.5": ["shikar"], "-1.2 7.4 6.1": ["ectasia"], "7.5 4.7 -3.0": ["arive"], "6.9 8.3 4.3": ["nonprogrammers"], "0.3 1.0 12.1": ["kanina"], "13.1 -0.4 15.2": ["plumetted", "testliner"], "4.0 10.0 6.7": ["qawwals"], "20.9 9.9 9.6": ["plasticised"], "12.7 5.1 15.7": ["everincreasing"], "5.4 19.9 8.5": ["scientistic"], "3.1 4.3 0.6": ["epoxides"], "-8.9 7.5 -3.4": ["lief"], "-0.8 9.5 3.4": ["unoptimized"], "5.8 10.1 10.2": ["hamams"], "-1.5 17.9 0.5": ["verballing"], "4.4 7.8 12.4": ["unstimulating"], "5.4 15.7 5.7": ["ultralite"], "-3.6 -3.8 3.9": ["pril"], "0.2 2.1 15.0": ["subcouncil"], "8.4 19.8 11.9": ["maundering"], "4.3 29.5 7.5": ["intransigently"], "14.0 11.3 22.6": ["osity"], "11.8 4.6 14.1": ["appliqu"], "8.2 24.1 12.6": ["injuriously"], "9.7 -1.9 34.3": ["francese"], "-6.4 12.0 11.2": ["nolled"], "1.6 9.7 13.6": ["caprock"], "16.5 12.2 4.8": ["lionheart"], "4.9 16.4 13.9": ["tryer"], "21.2 6.8 33.2": ["baozi"], "9.8 -0.6 16.1": ["christie"], "-1.9 -4.5 -0.0": ["subserviced"], "8.8 10.6 11.5": ["aparment"], "-0.4 20.2 16.3": ["lonesomeness"], "15.0 -2.7 20.8": ["leggier"], "4.4 23.2 3.7": ["indiscriminating"], "15.0 -6.1 16.5": ["xxl"], "-1.6 8.3 4.3": ["efferent"], "16.3 16.2 5.8": ["backscattered"], "9.2 6.4 14.5": ["charanga"], "10.3 23.0 14.5": ["creaturely"], "12.1 -1.9 37.9": ["chermoula"], "4.9 5.4 24.0": ["coquito"], "2.1 18.6 3.8": ["perjurious"], "13.9 9.8 21.5": ["unweathered"], "11.4 18.2 12.7": ["outercourse"], "3.7 7.0 9.5": ["eugenerobinson"], "4.3 5.2 17.9": ["mancations"], "13.3 3.2 15.9": ["innograd"], "14.8 2.1 26.8": ["ristra"], "3.4 15.7 10.4": ["extreamly"], "-2.9 24.3 7.0": ["dedovshchina"], "7.9 2.7 9.0": ["sociales"], "1.9 3.8 -1.6": ["complier"], "-2.6 0.1 2.4": ["divorcement"], "8.9 6.4 31.9": ["aguas"], "10.3 10.5 16.7": ["powersliding"], "2.3 14.3 10.3": ["herr"], "-9.0 4.4 5.8": ["inservices"], "6.8 1.6 16.4": ["gulab"], "-5.9 7.8 9.1": ["trainin"], "12.0 7.9 11.0": ["coquettishness"], "6.5 8.7 14.9": ["nonassignable"], "12.4 21.7 4.8": ["multiculturism"], "8.6 0.2 22.2": ["wheaten"], "9.0 7.2 19.1": ["sento"], "7.1 0.9 15.0": ["dary"], "15.9 9.2 13.3": ["stilletos"], "13.6 -2.9 -1.9": ["anagreement"], "11.2 9.6 10.6": ["hyperpolarized"], "4.6 7.7 10.1": ["nonsinging"], "11.7 6.9 23.1": ["toeside"], "8.0 0.3 34.6": ["boniato"], "9.6 5.5 13.1": ["entreprenurial"], "10.9 13.7 11.9": ["oneiric"], "6.2 11.0 18.6": ["rory"], "32.8 21.6 18.8": ["crablike"], "4.6 -5.8 4.0": ["ued"], "-0.1 5.5 16.2": ["micropropagation"], "3.8 3.6 -0.4": ["seasonopening"], "12.8 9.9 10.6": ["moviestar"], "-0.5 10.0 9.0": ["intraweek"], "2.1 3.9 0.4": ["rmed"], "3.2 6.6 8.1": ["acerbated"], "9.3 16.7 9.8": ["bandoleers"], "12.0 5.1 26.8": ["coracles"], "-4.1 6.6 10.5": ["antara"], "2.4 3.1 15.7": ["perscriptions"], "4.0 27.9 4.5": ["insurrectional"], "10.1 11.4 22.3": ["balds"], "11.2 0.2 2.3": ["featues"], "10.1 9.3 18.0": ["midshow"], "6.6 -0.9 6.0": ["peformers"], "17.2 18.7 6.6": ["consumerized"], "2.0 3.8 7.7": ["lfe"], "0.9 12.2 4.7": ["deionization"], "2.3 3.2 10.1": ["macroblocking"], "1.8 4.8 14.5": ["quantifications"], "10.2 10.5 11.9": ["pubilc"], "7.7 3.8 6.6": ["ammounts"], "5.5 0.3 15.5": ["familyfriendly"], "6.3 3.7 15.7": ["dits"], "15.1 -2.1 10.4": ["chlorovinyls"], "-0.2 8.0 8.9": ["dewar"], "15.0 24.7 2.0": ["narcoterrorist"], "9.8 2.4 3.3": ["cokemaking"], "16.8 7.3 16.3": ["plastinate"], "13.6 14.7 4.1": ["blanker"], "7.5 24.3 8.0": ["shamefulness"], "0.4 -7.2 6.1": ["intercampus"], "10.1 4.9 14.2": ["pfd"], "5.7 8.3 2.8": ["matchmake"], "11.8 -2.3 4.2": ["megaplan"], "21.3 8.4 23.7": ["lobelias"], "6.5 9.7 6.0": ["interfamily"], "-4.3 9.6 0.9": ["glenohumeral"], "4.9 5.1 5.5": ["andsaid"], "13.2 14.0 8.3": ["ardous"], "17.3 9.3 18.4": ["wallies"], "13.9 21.2 9.7": ["durned"], "7.5 12.7 9.9": ["debilities"], "6.1 23.9 15.8": ["overshift"], "0.9 10.0 4.2": ["acrimonies"], "6.7 9.7 20.5": ["cotyledon"], "-1.4 8.2 7.9": ["epigraphic"], "-7.2 -1.9 6.7": ["enaction"], "12.9 18.3 5.0": ["cartographical"], "27.3 5.8 10.9": ["cashcall"], "0.6 4.9 9.1": ["themoney"], "8.4 3.3 16.7": ["abir"], "7.6 14.5 8.5": ["loook"], "9.5 2.5 -0.1": ["tld"], "-4.7 6.6 6.7": ["triangulars"], "12.4 3.5 23.6": ["homebaked"], "12.2 18.4 7.7": ["potus"], "13.6 13.3 8.1": ["lobbiest"], "2.6 1.7 11.4": ["tenorman"], "-1.4 25.8 3.8": ["prosecutive"], "12.2 3.3 10.0": ["newegg"], "19.0 17.3 17.8": ["strobed"], "9.9 7.4 13.0": ["wimples"], "16.0 8.5 21.8": ["dippin"], "5.6 -1.2 11.6": ["temporada"], "3.6 -1.2 -0.4": ["parecoxib"], "20.4 5.0 29.1": ["candlestand"], "5.7 8.0 12.0": ["paleomagnetic"], "17.3 -0.2 24.4": ["saurus"], "11.3 3.9 8.1": ["minimizer"], "2.3 -0.4 14.8": ["canalised"], "5.1 9.7 -4.0": ["sequestrate"], "1.7 1.1 1.8": ["subaccounting"], "11.6 24.3 0.6": ["nulcear"], "-2.6 0.3 12.8": ["rebreeding"], "-3.5 4.5 13.2": ["saccharide"], "6.3 -4.0 11.9": ["thomson"], "14.7 12.4 23.6": ["selkie"], "6.7 6.3 13.8": ["nagaswaram"], "-5.1 4.7 8.2": ["isogenic"], "2.3 23.4 11.1": ["defenestrate"], "2.7 9.5 4.7": ["fracced"], "1.6 2.5 20.7": ["tinta"], "9.0 21.0 8.5": ["sophistical"], "19.1 6.5 35.5": ["pinchos"], "9.2 3.6 7.8": ["leadman"], "-0.5 15.1 10.4": ["malum"], "5.4 6.4 15.7": ["homelier"], "17.1 7.9 13.9": ["reshingle"], "7.9 15.3 18.6": ["inoffensiveness"], "-5.1 0.6 8.3": ["breastcancer"], "3.7 16.7 23.5": ["kiter"], "-0.3 18.9 1.2": ["philosophises"], "-4.4 16.5 8.1": ["objectionably"], "7.6 6.2 19.0": ["bettin"], "4.2 3.9 13.8": ["capa"], "7.9 5.1 14.4": ["reprovisioning"], "20.8 7.0 10.1": ["superskinny"], "7.8 1.0 14.0": ["raleigh"], "15.3 13.2 19.3": ["orangeade"], "4.4 17.4 10.7": ["eths"], "10.4 7.8 5.1": ["backlists"], "1.5 2.9 13.7": ["alist"], "0.9 5.1 15.8": ["statuatory"], "4.0 14.0 16.3": ["villanelle"], "15.1 13.9 20.1": ["panner"], "11.1 24.0 5.8": ["airbenders"], "6.8 5.2 12.5": ["fishwrap"], "18.2 19.6 11.8": ["exiguous"], "-1.9 15.5 14.5": ["khabroo"], "7.5 14.2 9.5": ["speedbreaker"], "8.3 12.4 14.8": ["saggin"], "-2.5 2.3 7.7": ["newsbreaks"], "12.9 -1.7 5.0": ["inlude"], "2.9 3.4 18.4": ["skinfold"], "-2.3 -15.6 1.0": ["theprogram"], "8.7 11.5 25.5": ["kokum"], "15.3 4.0 12.3": ["drawed"], "8.7 8.2 17.0": ["monoski"], "8.4 9.6 12.7": ["lindsey"], "12.7 8.1 6.0": ["moneylaundering"], "0.5 15.9 7.0": ["extraverts"], "-1.6 10.6 3.5": ["responsabilities"], "5.4 22.3 4.5": ["reverance"], "12.4 1.3 7.1": ["iinet"], "20.8 0.6 6.6": ["hanarotelecom"], "0.5 -4.5 10.8": ["iana"], "-8.7 3.7 0.7": ["classman"], "2.4 6.3 17.3": ["ambrotype"], "-2.9 -3.9 1.4": ["custodied"], "15.4 8.9 17.3": ["dickie"], "0.0 1.1 -1.2": ["theperiod"], "1.4 11.4 10.9": ["possition"], "9.9 11.4 14.0": ["tenderfoots"], "1.9 8.7 30.2": ["vaka"], "4.9 9.5 11.9": ["shtml"], "4.1 18.4 12.8": ["acculturating"], "9.0 10.1 8.5": ["topographer"], "-2.5 11.8 10.7": ["noninstitutionalized"], "7.7 13.5 12.4": ["alseep"], "10.4 3.2 -14.8": ["establishement"], "11.7 10.8 23.8": ["tackers"], "15.5 16.9 18.6": ["nanocell"], "7.8 7.8 10.0": ["nuggetty"], "6.3 18.9 12.4": ["sistahs"], "13.3 21.1 7.2": ["blandishment"], "5.0 11.8 12.3": ["speccing"], "-4.6 16.9 0.7": ["shahs"], "3.6 12.0 5.4": ["mucinous"], "7.3 15.6 19.6": ["complected"], "11.3 2.8 2.9": ["newsiest"], "4.6 2.3 13.2": ["nonracing"], "14.8 20.2 25.6": ["stickum"], "17.9 13.1 10.2": ["brander"], "-1.8 2.1 1.2": ["traunches"], "15.9 12.5 8.0": ["postmillennial"], "5.1 2.5 5.9": ["thalidomiders"], "5.8 10.0 7.3": ["sirius"], "1.0 13.0 1.8": ["photoemission"], "2.1 12.3 12.3": ["journies"], "-2.4 11.2 9.9": ["transitionally"], "4.3 11.4 -1.0": ["sevaks"], "-5.6 5.9 6.6": ["chael"], "-3.7 -9.5 8.4": ["wkly"], "5.8 7.2 -7.0": ["parachurch"], "3.9 5.9 10.0": ["trid"], "7.4 -0.7 15.3": ["marcha"], "8.0 9.0 12.9": ["chockers"], "17.5 -2.5 23.4": ["acqua"], "13.7 6.1 25.8": ["pavlovas"], "3.6 4.8 4.4": ["werer"], "8.6 10.0 19.7": ["megavideo"], "-1.6 3.9 -5.9": ["misusers"], "11.3 1.4 9.0": ["designerwear"], "4.6 14.4 19.4": ["minehunters"], "1.8 0.5 4.1": ["qq"], "-3.2 15.6 -4.2": ["organiztion"], "1.5 12.6 11.7": ["teleconverter"], "-0.3 13.1 19.5": ["rives"], "15.6 4.5 19.0": ["rosetta"], "-4.8 5.7 13.0": ["nonmarried"], "24.9 23.3 9.8": ["terraformed"], "10.5 7.6 18.8": ["reese"], "-4.1 -2.1 7.7": ["sucralfate"], "12.2 8.5 10.0": ["hydrolic"], "12.2 7.1 3.8": ["autoblog"], "6.5 25.3 -0.0": ["irreconcilability"], "13.5 1.1 25.4": ["ocarinas"], "15.4 14.6 34.2": ["bolognaise"], "19.1 6.5 20.2": ["yellowwood"], "-1.5 6.1 12.0": ["ryokans"], "14.1 10.0 15.8": ["herman"], "5.2 -1.4 9.5": ["coi"], "9.2 9.1 9.3": ["chancre"], "7.5 2.8 15.7": ["muxes"], "11.7 11.3 8.8": ["bitchslap"], "7.0 8.1 11.7": ["megapolitan"], "0.1 9.1 -0.7": ["importants"], "11.0 12.5 19.0": ["windsurfs"], "-4.7 1.4 18.3": ["vouchered"], "3.9 15.5 8.7": ["theologists"], "8.2 13.1 5.7": ["fornt"], "-0.4 9.8 6.7": ["hatten"], "8.7 22.0 12.0": ["backfeed"], "4.3 9.5 5.0": ["overread"], "3.8 7.3 10.3": ["variograms"], "12.9 9.0 26.8": ["kofte"], "17.5 13.0 14.8": ["wagamama"], "-2.3 10.7 5.8": ["garu"], "10.8 12.6 37.2": ["fulmar"], "7.8 10.8 10.8": ["complicatedly"], "19.2 10.1 23.3": ["grabbin"], "9.3 14.8 11.9": ["bagua"], "8.5 6.9 16.6": ["frize"], "5.6 20.2 14.3": ["tautologies"], "3.8 -0.6 10.7": ["ecently"], "16.0 11.6 30.2": ["bulbuls"], "15.9 7.0 3.5": ["loadsamoney"], "19.8 20.1 16.3": ["pinheaded"], "12.6 3.3 13.7": ["nora"], "10.4 23.0 10.8": ["dissemblers"], "9.5 -1.5 2.8": ["saddlestitcher"], "3.1 8.6 4.3": ["metacritic"], "1.7 4.4 5.9": ["sulfation", "cicletanine"], "4.3 15.2 15.7": ["bioregions"], "11.6 29.4 6.6": ["formidability"], "5.4 -10.8 4.1": ["worklists"], "4.3 3.8 16.4": ["ventura"], "6.7 12.0 13.4": ["microtones"], "6.7 6.1 19.3": ["sprayfield"], "0.0 -7.2 -0.8": ["sahn"], "1.5 6.6 18.6": ["nha"], "6.0 18.2 12.8": ["unaffectionate"], "1.6 1.3 -1.6": ["recuiting"], "-3.4 13.1 4.9": ["unmandated"], "-4.3 27.1 -0.2": ["civilianized"], "11.5 9.9 20.3": ["mondays"], "3.8 6.8 8.2": ["circumambulate"], "4.3 7.8 23.3": ["bareroot"], "7.9 15.4 23.7": ["pipistrelle"], "4.5 10.7 3.9": ["severa"], "4.1 -4.3 1.9": ["convenings"], "12.0 12.3 9.6": ["mapplets"], "8.4 20.2 8.8": ["contumely"], "22.6 21.7 10.6": ["tanklike"], "2.2 6.1 8.4": ["mena"], "0.4 8.8 -4.2": ["marketin"], "4.6 19.0 11.9": ["thougt"], "-0.3 13.1 10.0": ["hemianopia"], "15.0 2.2 9.5": ["coppersmiths"], "5.6 2.7 6.9": ["unchaged"], "11.5 13.0 24.9": ["brindled"], "12.8 16.7 0.9": ["dimensionalized"], "21.7 22.0 37.8": ["anole"], "6.3 8.2 4.4": ["yardmaster"], "13.6 6.9 10.3": ["fructification"], "14.2 9.5 16.5": ["fluorescently"], "6.3 5.8 11.4": ["camellos"], "7.5 11.7 19.0": ["spellbind"], "2.7 9.6 13.9": ["nucleolin"], "-3.6 11.4 6.4": ["mandatum"], "15.2 18.6 11.6": ["weariest"], "-4.2 13.9 8.0": ["snicko"], "12.5 6.3 5.1": ["photometers"], "-3.5 4.0 4.8": ["tyo"], "3.8 4.3 9.9": ["fooding"], "15.6 3.6 14.2": ["bathmats"], "9.2 23.8 3.1": ["lamestream"], "8.3 14.3 0.7": ["electroweak"], "2.5 -1.0 14.9": ["yg"], "12.4 12.8 5.5": ["timein"], "12.1 8.6 -0.9": ["legitamate"], "8.3 11.5 22.3": ["intercrop"], "-5.9 -1.0 4.9": ["agenesis"], "11.3 -1.8 10.4": ["zucchettos"], "7.0 8.7 4.8": ["benz"], "3.4 16.7 13.9": ["supsect"], "8.6 26.3 8.1": ["metonymy"], "13.5 -1.3 15.5": ["pluri"], "11.1 8.5 4.3": ["devloping"], "16.1 15.9 4.6": ["immiment"], "9.2 5.1 15.5": ["midoff"], "-1.6 6.8 13.0": ["rostral"], "7.5 5.2 9.5": ["showbands"], "-1.7 2.2 5.2": ["unsignable"], "3.2 19.6 20.7": ["dews"], "13.0 0.0 17.8": ["didjeridu"], "2.6 1.9 4.6": ["latrepirdine"], "9.4 1.3 17.0": ["suitcoat"], "10.9 26.5 10.1": ["defocusing"], "0.7 9.4 8.8": ["operons"], "13.7 12.2 10.5": ["alar"], "11.1 14.1 19.8": ["achin"], "-2.0 -3.5 5.6": ["paramedicine"], "2.2 3.5 -3.0": ["agovernment"], "13.8 6.3 12.1": ["gigaflop"], "2.2 -3.9 7.3": ["requete"], "12.4 10.2 26.5": ["ohia"], "-5.9 8.4 14.8": ["femtogram"], "20.5 2.1 -2.1": ["trainmaker"], "14.5 9.1 1.7": ["originial"], "-5.3 19.5 2.7": ["percepts"], "6.3 14.3 13.6": ["meagerness"], "15.5 13.3 4.2": ["skilfull"], "-10.7 25.0 8.6": ["criticals"], "17.0 10.0 -10.2": ["delver"], "17.6 3.1 6.0": ["comsumer"], "8.9 13.7 12.2": ["paedos"], "-6.8 14.1 5.3": ["fluoropyrimidine"], "7.9 14.6 5.9": ["obession"], "17.7 13.2 22.6": ["taxidermic"], "-4.5 1.2 8.0": ["linting"], "-5.7 34.0 7.7": ["talibans"], "9.8 21.1 5.5": ["enmeshes"], "16.3 19.8 5.7": ["boxings"], "8.0 7.0 3.4": ["picketline"], "1.6 27.1 2.8": ["delegitimation"], "4.8 -3.5 5.6": ["sbc"], "3.3 22.4 8.3": ["outlawry"], "5.7 17.5 4.2": ["customes"], "23.0 16.3 30.9": ["froggie"], "12.0 15.9 15.4": ["darky"], "-7.6 8.5 3.1": ["insertive"], "-0.3 11.2 12.4": ["overraced"], "6.4 24.5 12.6": ["unbelievability"], "2.2 10.0 9.0": ["taj"], "7.2 21.7 16.6": ["intransitive"], "-5.5 4.6 9.7": ["nonfarming"], "15.4 5.0 24.9": ["uppy"], "3.5 21.9 -1.9": ["unrightfully"], "6.8 -1.4 15.7": ["onlays"], "14.1 9.4 13.8": ["imaginarium"], "7.6 8.8 -1.7": ["msdn"], "3.3 4.1 11.6": ["pamahalaan"], "17.0 9.4 31.5": ["munchy"], "2.8 3.3 6.8": ["kudi"], "10.9 2.5 7.3": ["totale"], "4.4 5.0 13.9": ["bicentennials"], "11.3 5.8 15.3": ["groot"], "-3.1 13.6 5.8": ["standardless"], "8.2 -2.1 7.9": ["integra"], "8.6 9.1 -3.1": ["minicam"], "5.2 13.8 6.9": ["tanding"], "13.3 7.8 21.7": ["viridis"], "6.7 20.0 15.0": ["overmanaging"], "11.4 14.4 22.0": ["whatsits"], "-2.1 26.3 5.4": ["fratricides"], "17.1 -10.1 -0.4": ["eletronic"], "7.6 14.7 10.4": ["downhilling"], "11.6 -2.2 5.5": ["airlaid"], "3.2 5.4 17.6": ["raglan"], "15.9 20.1 3.1": ["prerendered"], "-4.9 2.3 12.3": ["nanalo"], "12.7 13.5 6.3": ["assetts"], "8.7 27.5 18.4": ["anthropocentrism"], "12.9 8.0 0.9": ["outsidethe"], "16.1 11.9 12.5": ["alllll"], "-8.2 -0.9 12.0": ["nonrestricted"], "4.4 10.3 15.2": ["pedallers"], "-4.2 5.3 -2.1": ["mindblower"], "3.6 11.9 10.4": ["movieoke"], "-0.5 18.4 12.7": ["kismat"], "2.6 7.5 3.1": ["civile"], "0.1 1.0 9.6": ["parklets"], "8.4 14.3 10.4": ["chaning"], "18.6 12.8 15.8": ["undulant"], "11.3 9.5 7.9": ["thumbboard"], "34.6 2.0 7.8": ["gearmaker"], "5.9 13.8 8.7": ["pheras"], "-9.5 10.4 2.6": ["reponsibilities"], "0.9 19.0 4.2": ["undeleted"], "-0.6 15.7 4.6": ["braindump"], "5.9 -2.8 13.3": ["ardal"], "-4.0 0.7 4.7": ["danazol"], "0.2 -1.5 11.9": ["surger"], "13.5 8.1 6.8": ["backpages"], "-4.9 2.4 0.3": ["backfiles"], "19.1 12.0 13.7": ["syst"], "7.8 26.2 -0.1": ["dispensationalists"], "12.0 5.2 9.9": ["checkstands"], "4.2 6.0 3.8": ["schmidt"], "8.1 10.6 2.9": ["trustmarks"], "3.7 14.4 3.9": ["factless"], "-0.5 0.2 7.8": ["hris"], "6.9 11.3 7.2": ["dependently"], "14.1 5.9 16.0": ["replumb"], "2.5 12.3 -1.3": ["illegalize"], "-3.0 -7.8 10.5": ["undeposited"], "7.5 11.3 5.4": ["meida"], "14.2 5.7 7.3": ["advt"], "25.0 1.4 17.1": ["giltwood"], "4.6 0.5 14.5": ["hwn"], "3.0 15.1 21.1": ["microcystins"], "10.2 17.4 9.5": ["jezebel"], "17.0 15.0 30.3": ["indentions"], "8.4 5.5 14.0": ["laserdiscs"], "-1.6 7.1 10.2": ["nucleases"], "6.4 14.6 7.3": ["ofmy"], "8.3 6.2 13.7": ["culturati"], "9.8 28.7 12.2": ["pathless"], "-2.3 13.3 5.0": ["diachronic"], "10.7 -3.6 2.3": ["fieldhouses"], "5.8 16.6 9.6": ["playhead"], "-1.1 17.0 11.4": ["psychologizing"], "32.0 20.3 8.5": ["megacorp"], "3.8 2.2 8.9": ["linup"], "1.8 8.7 19.3": ["diay"], "12.4 -1.7 18.6": ["addax"], "-1.7 2.8 1.8": ["decompensated"], "20.9 13.2 10.6": ["spaceliner"], "5.9 -2.4 -0.8": ["vitch"], "-2.3 19.3 11.5": ["portzline"], "-2.6 11.3 7.0": ["covere"], "9.2 8.8 13.2": ["motard"], "0.9 -0.4 -1.8": ["organzations"], "3.6 28.0 4.4": ["terroism"], "14.0 24.6 3.3": ["megalomanic"], "-4.4 25.8 5.1": ["noncoms"], "16.2 8.6 20.0": ["crania"], "17.3 16.7 7.5": ["virutally"], "0.8 19.0 10.9": ["incivilities"], "5.4 26.2 3.2": ["hidding"], "2.4 -5.8 3.4": ["presention"], "-4.4 8.9 6.1": ["strugged"], "10.3 5.7 16.4": ["putties"], "6.6 24.3 11.0": ["chokingly"], "-3.4 6.5 -2.0": ["nonprivileged"], "3.8 14.2 -1.5": ["theatening"], "12.2 7.0 15.2": ["splashbacks"], "15.4 1.2 17.1": ["tren"], "11.6 5.3 2.4": ["subscibers"], "-4.3 -1.8 2.0": ["visitability"], "-6.6 13.0 0.8": ["deductor"], "0.5 16.8 11.6": ["referree"], "12.5 2.6 7.7": ["inovation"], "20.6 16.1 6.7": ["camming"], "-0.3 7.4 11.9": ["biodynamically"], "6.1 8.3 12.9": ["anns"], "18.9 3.9 40.7": ["cloudberries"], "1.5 24.8 4.9": ["dependences"], "5.5 -1.0 8.8": ["coxib"], "7.2 14.7 11.2": ["vivify"], "7.4 16.3 21.9": ["maia"], "10.6 12.2 33.4": ["bunchgrass"], "5.9 12.9 10.2": ["flamini"], "2.4 8.4 6.6": ["async"], "2.7 6.1 4.3": ["manycore"], "7.7 9.1 13.1": ["tting"], "7.2 3.7 19.8": ["bustouts"], "-6.2 8.5 -2.3": ["missiologist"], "3.4 6.5 18.0": ["katoa"], "11.9 9.1 15.2": ["goldie"], "4.2 12.5 19.4": ["anticyclonic"], "16.2 2.3 -1.2": ["housands"], "5.8 7.6 0.0": ["stetch"], "6.6 4.0 22.9": ["kok"], "7.3 8.8 15.3": ["fernando"], "0.5 -0.9 2.4": ["retrun"], "5.0 14.6 13.0": ["kojacked"], "7.3 23.0 9.1": ["braggadocious"], "6.1 3.3 7.0": ["phenoxyethanol"], "-0.3 5.0 5.3": ["midwived"], "16.4 4.9 2.4": ["retile"], "6.1 22.4 25.6": ["splitty"], "-4.5 4.7 8.3": ["zonals"], "12.1 6.2 40.7": ["tako"], "11.8 7.5 13.8": ["winterised"], "11.5 19.2 19.7": ["foilage"], "-3.6 18.8 1.9": ["prooved"], "10.1 17.3 7.7": ["vivified"], "17.1 8.4 30.7": ["kiawe"], "0.7 -0.4 14.9": ["refreshening"], "13.6 20.5 12.3": ["uncomprehensible"], "8.6 5.7 11.0": ["agglutination"], "14.9 8.0 3.1": ["uncertainy"], "-5.5 6.9 2.2": ["jeevan"], "-2.3 1.0 7.9": ["nondiagnostic"], "4.2 21.1 10.7": ["bashert"], "3.7 2.2 3.9": ["lightpoint"], "1.4 4.8 12.2": ["conductivities"], "5.7 13.0 8.5": ["pleiotropic"], "7.8 5.9 11.8": ["couleur", "threepenny"], "-1.6 10.5 7.3": ["excersise"], "-4.5 6.6 8.5": ["certaines"], "0.9 -4.5 -1.0": ["recordists"], "9.6 3.0 17.4": ["turfites"], "12.0 15.7 12.9": ["halfboards"], "7.8 17.7 7.9": ["frontbenches"], "3.7 20.6 13.0": ["safetys"], "7.6 2.4 12.8": ["fuentes"], "7.7 8.3 20.0": ["brickfields"], "2.3 8.1 -2.5": ["interactors"], "11.2 6.4 14.1": ["garbo"], "6.7 -0.2 9.2": ["leed"], "8.6 22.3 10.7": ["perfectness"], "14.0 9.3 24.0": ["cocklebur"], "3.2 12.7 13.0": ["seventysomething"], "1.5 -1.0 -2.1": ["icluding"], "14.3 0.9 38.6": ["ballotine"], "9.6 4.2 2.7": ["nonsterile"], "5.9 -6.9 12.7": ["replacers"], "3.2 5.4 24.5": ["holidaymaking"], "10.2 6.0 6.7": ["supergoal"], "7.6 23.3 12.8": ["wirecutters"], "16.7 14.2 6.4": ["untrackable"], "-0.3 14.3 17.1": ["buat"], "1.4 0.4 2.5": ["forexlive"], "14.3 4.0 4.5": ["stadion"], "11.4 4.5 8.8": ["syringed"], "14.4 0.2 22.6": ["sinamay"], "4.0 10.9 9.4": ["sappier"], "-4.0 13.7 4.7": ["clearable"], "24.7 19.9 17.1": ["sidewinders"], "11.0 13.9 17.7": ["unaffectedly"], "7.3 12.6 8.9": ["goyish"], "1.7 5.0 10.0": ["itse"], "3.6 13.0 14.0": ["itni"], "-2.3 1.6 2.7": ["intime"], "3.1 0.1 6.8": ["businessowner"], "8.6 8.7 16.0": ["earthern"], "6.3 13.1 8.5": ["setout"], "6.6 10.0 -1.1": ["bidirectionally"], "0.8 10.9 2.4": ["pecial"], "0.4 9.5 3.9": ["weldability"], "15.9 5.2 11.1": ["rattiest"], "10.8 24.5 8.7": ["artificer"], "7.0 22.7 -4.4": ["indespensible"], "2.8 15.2 4.2": ["autodidactic"], "17.2 2.8 15.3": ["costco"], "-2.1 -7.6 7.5": ["hahn"], "6.2 9.4 8.7": ["romo"], "6.3 17.7 8.9": ["theycan"], "-0.8 13.8 13.8": ["endogamy"], "13.9 8.2 1.3": ["disppointing"], "-7.7 6.3 3.4": ["shiksha"], "-2.9 18.7 1.0": ["phonebanking"], "1.2 9.7 2.2": ["pupillary"], "1.4 10.9 5.3": ["domiciling"], "16.2 19.9 7.0": ["antechambers"], "10.0 17.7 19.9": ["diphthongs"], "7.8 15.9 12.2": ["depressionary"], "-8.8 6.6 1.0": ["nonpsychotic"], "12.1 12.3 14.1": ["crat"], "0.6 1.9 8.0": ["simethicone"], "-7.4 14.2 6.2": ["bracha"], "15.5 10.3 15.7": ["tympanic"], "-3.8 1.1 9.8": ["antiphon"], "20.2 5.6 10.5": ["headware"], "17.3 2.2 2.2": ["clubcard"], "3.4 14.0 7.9": ["admitedly"], "-7.6 -0.4 13.6": ["ngam"], "19.2 3.0 17.4": ["quare"], "6.2 17.6 1.4": ["reenforce"], "7.1 12.3 22.4": ["abelia"], "8.3 16.7 16.0": ["sitout"], "-2.7 -4.0 4.2": ["agao"], "6.6 12.8 15.7": ["pornographically"], "13.4 4.4 7.3": ["redfaced"], "18.9 17.1 3.8": ["triumvirates"], "-2.3 -4.5 2.5": ["meniscectomy"], "13.3 10.2 16.9": ["hurrican"], "-3.2 3.1 15.2": ["lumabas"], "4.4 5.9 12.8": ["granodioritic"], "8.9 -5.2 -2.6": ["attacted"], "12.4 11.9 12.2": ["doorknockers"], "4.6 10.0 12.1": ["neurocircuitry"], "14.2 17.9 15.7": ["handicam"], "7.6 7.8 8.5": ["jasmonate"], "4.3 20.2 5.8": ["gamplay"], "-1.4 7.3 -1.1": ["devisees"], "11.6 5.2 6.7": ["slobbing"], "-0.6 -0.0 7.1": ["nimodipine"], "-0.1 22.1 15.3": ["ultimates"], "5.8 18.5 5.7": ["admirations"], "8.4 18.9 20.4": ["rares"], "21.0 29.9 20.0": ["fiercesome"], "1.6 8.4 -1.8": ["jailhouses"], "9.2 0.2 11.2": ["espera"], "-5.0 0.4 5.6": ["concertmistress"], "4.7 2.2 1.4": ["imidazole"], "0.5 12.4 -5.6": ["highranking"], "0.5 18.4 3.1": ["condolances"], "1.0 -4.4 30.7": ["ackees"], "16.3 14.2 13.6": ["handtools"], "17.7 14.9 12.6": ["whathaveyou"], "4.6 -5.6 -7.6": ["rehabilation"], "-1.5 -2.1 8.6": ["mepivacaine"], "12.7 16.6 29.9": ["parasailers"], "6.4 -1.8 8.1": ["lahn"], "2.4 1.7 15.7": ["dhara"], "12.1 20.5 15.2": ["tunein"], "5.8 14.4 7.5": ["bleepers"], "15.4 8.6 7.3": ["anaylsts"], "24.5 6.6 16.6": ["alicious"], "6.4 2.5 25.9": ["knotless"], "0.9 7.8 5.1": ["playspaces"], "-0.9 11.3 5.8": ["endophenotypes"], "-9.2 1.7 4.3": ["preinjury"], "7.6 2.9 11.4": ["varias"], "1.7 14.2 14.6": ["unta"], "2.3 2.1 11.4": ["clase"], "9.2 12.7 20.2": ["mahjongg"], "14.5 -2.4 39.7": ["frys"], "5.1 11.9 14.3": ["aapka"], "19.9 19.1 2.6": ["megaleak"], "10.2 14.3 9.2": ["bagginess"], "-3.4 5.7 -3.3": ["virture"], "5.3 17.1 18.1": ["dependables"], "7.9 5.1 6.1": ["aucun"], "16.8 4.2 19.5": ["headstocks"], "0.7 19.6 3.2": ["muhtar"], "3.3 -2.5 10.5": ["hypercholesterolemic"], "15.4 -0.9 15.6": ["mornng"], "5.7 13.4 15.3": ["rivaly"], "10.2 15.6 9.9": ["boycotter"], "5.5 7.3 -0.3": ["notating"], "5.5 13.6 17.2": ["determinates"], "-3.8 4.3 4.5": ["reccurring"], "11.4 24.4 5.9": ["weild"], "8.6 5.0 15.6": ["quatro"], "3.2 -9.6 4.7": ["montagne"], "8.1 4.0 5.4": ["colle"], "8.2 -3.2 17.3": ["caseinates"], "14.8 11.0 11.9": ["recontextualizing"], "9.4 6.6 19.1": ["sarma"], "-4.4 12.9 9.7": ["biographically"], "12.7 5.6 2.4": ["electrophotographic"], "4.3 11.4 8.5": ["phagosomes"], "0.3 6.9 9.5": ["comunities"], "14.8 5.2 12.9": ["orginial"], "4.1 14.8 14.3": ["jitsu"], "4.1 7.2 17.1": ["heterotrophic"], "-5.6 20.0 7.8": ["decentralist"], "4.6 15.5 16.5": ["drollness"], "2.5 8.1 21.0": ["plastids"], "10.3 5.6 0.7": ["renouned"], "10.4 5.8 13.2": ["ography"], "9.3 9.2 17.9": ["soleplate"], "14.3 10.6 45.8": ["hilsha"], "6.7 15.4 17.9": ["poolie"], "2.2 -0.2 21.3": ["pagkain"], "2.3 3.6 14.9": ["vik"], "16.0 11.8 15.6": ["farmgirl"], "7.4 4.3 9.2": ["drie"], "-15.7 11.9 3.1": ["mujtahid"], "5.4 4.6 7.7": ["bastante"], "17.3 13.9 33.2": ["noddy"], "2.2 24.9 9.6": ["dadas"], "-2.8 0.5 8.8": ["rehersals"], "10.4 1.9 10.3": ["arecord"], "11.4 3.8 11.1": ["consessions"], "-1.5 9.6 12.4": ["adrenocortical"], "14.8 2.6 6.0": ["zuma"], "19.1 12.5 18.4": ["polystone"], "-1.3 4.1 17.1": ["mayroon"], "12.1 -2.4 25.2": ["cruiseships"], "11.7 16.9 7.3": ["latifundia"], "4.3 15.6 -2.5": ["degaussers"], "-5.6 14.6 6.2": ["leniencies"], "-4.7 7.0 7.2": ["itl"], "15.6 10.7 30.6": ["colobus"], "2.1 22.1 8.5": ["polarisations"], "8.7 0.8 9.3": ["jugar"], "16.6 4.8 3.2": ["braniac"], "1.6 -4.1 21.2": ["kemp"], "-7.8 10.2 8.5": ["mentation"], "-3.0 19.3 4.3": ["scrupulosity"], "1.4 2.0 6.9": ["ured"], "-3.0 0.9 3.5": ["piroxicam"], "4.9 14.6 12.7": ["ganna"], "-1.4 9.5 4.9": ["proapoptotic"], "4.4 8.6 10.9": ["destressing"], "3.3 -6.0 5.5": ["earthday"], "2.4 11.7 8.9": ["demonetized"], "12.4 6.4 13.1": ["geodynamics"], "8.5 10.1 20.3": ["haem"], "9.9 12.7 36.4": ["ilish"], "9.4 11.9 11.5": ["gruelingly"], "15.2 17.3 -1.8": ["establisment"], "-2.7 20.0 2.6": ["enumerable"], "1.4 9.6 4.4": ["unexcitable"], "10.2 3.1 8.1": ["whipsmart"], "2.0 9.5 9.4": ["wome"], "7.1 -6.9 7.2": ["signin"], "14.3 6.1 39.8": ["escalopes"], "10.3 18.2 1.2": ["dominace"], "-0.7 22.3 2.4": ["decolonizing"], "-0.3 8.9 0.6": ["transactivation"], "2.2 -4.2 -1.7": ["radiolabelled"], "-6.3 -2.5 4.4": ["luteal"], "3.5 15.4 4.4": ["envrionment"], "7.1 -2.3 14.1": ["polycart"], "2.6 2.0 9.5": ["mahotsav"], "5.8 7.5 19.2": ["organochlorine"], "14.5 1.6 5.8": ["neoteric"], "7.6 19.8 11.3": ["easilly"], "9.3 4.4 4.4": ["clix"], "9.5 21.8 7.9": ["blondest"], "24.8 11.1 13.4": ["moptops"], "7.1 14.8 20.7": ["fru"], "6.6 3.6 12.8": ["coextrusion"], "0.4 -4.7 5.2": ["gelnique"], "7.1 9.0 6.1": ["podcatcher"], "11.4 2.2 14.3": ["dalle"], "-4.1 3.0 -4.3": ["ql"], "16.2 13.2 12.7": ["permenantly"], "12.1 11.0 5.4": ["arcminutes"], "5.5 2.6 3.5": ["monosilane"], "-5.4 2.4 11.3": ["thesping"], "13.7 6.1 30.1": ["krathong"], "17.5 12.8 25.9": ["drooly"], "22.2 8.1 5.5": ["bossnapping"], "13.2 1.1 12.5": ["hundereds"], "15.7 18.5 2.6": ["standy"], "1.5 4.5 4.8": ["parivaar"], "11.0 15.8 26.2": ["dolphinariums"], "14.5 7.6 10.5": ["thobes"], "8.7 10.1 12.4": ["chopines"], "17.4 15.8 17.3": ["dankness"], "2.0 6.0 14.2": ["eluent"], "10.8 4.1 0.6": ["technologyand"], "1.8 5.9 3.5": ["submaximal"], "5.8 8.4 11.1": ["spectrin"], "1.7 8.3 5.6": ["trabedersen"], "2.0 -11.0 -10.3": ["inconjunction"], "14.5 14.2 16.5": ["gnashes"], "8.5 16.4 13.3": ["backland"], "9.2 25.5 7.9": ["philosophes"], "4.1 7.0 -5.4": ["strenghtens"], "7.8 7.8 22.9": ["granddog"], "21.6 8.1 8.2": ["wallstreet"], "1.3 -1.1 4.7": ["polyelectrolyte"], "6.6 6.8 12.5": ["puled"], "12.2 10.3 14.8": ["euphonic"], "5.4 7.9 9.6": ["charidee"], "4.3 12.7 9.1": ["messers"], "-1.3 11.8 8.7": ["fringey"], "2.8 11.2 6.8": ["talki"], "4.5 0.2 6.6": ["bisa"], "8.7 10.7 11.1": ["bedazzlement"], "-5.7 15.6 7.5": ["aayi"], "5.9 15.4 7.2": ["chanelling"], "6.6 12.7 14.7": ["deceasing"], "9.3 4.4 13.1": ["togeather"], "15.2 15.5 13.0": ["declarers"], "23.0 4.3 8.1": ["plushly"], "14.3 10.8 27.5": ["flintknapping"], "9.7 7.2 7.0": ["flexy"], "11.8 12.8 17.4": ["lamebrained"], "17.4 13.4 14.6": ["unstirred"], "7.1 2.0 12.3": ["openoffice"], "18.2 11.4 15.3": ["tagalongs"], "2.9 8.7 12.8": ["jeg"], "4.9 4.0 18.5": ["supercontinuum"], "14.7 2.5 6.8": ["conventionals"], "14.2 9.7 19.4": ["pucksters"], "6.4 4.8 9.4": ["gasolina"], "1.1 23.1 16.0": ["readerly"], "-0.7 3.0 9.7": ["nontender"], "20.5 26.0 12.6": ["smatter"], "2.5 12.3 -4.5": ["serbian"], "15.9 8.1 11.0": ["feminising"], "-0.2 -2.7 6.8": ["artgallery"], "9.9 20.6 8.7": ["highscore"], "-1.9 -0.8 13.2": ["guargum"], "-3.1 11.6 5.5": ["nanomolar"], "-2.9 4.5 11.4": ["spinsterish"], "13.7 15.8 27.6": ["indigos"], "-6.0 -2.3 8.4": ["rence"], "-2.5 14.0 6.6": ["votings"], "-7.2 3.0 1.4": ["unf"], "18.4 18.5 8.9": ["grapping"], "10.0 2.0 4.4": ["cybercities"], "10.8 18.7 18.2": ["snuggler"], "1.5 13.3 17.7": ["paltriest"], "0.2 12.5 11.2": ["ikaw"], "10.9 7.2 13.2": ["pallete"], "4.0 31.9 3.5": ["terrrorism"], "10.9 2.8 11.4": ["toea"], "-2.2 9.4 1.7": ["racemate"], "-1.4 -2.9 5.4": ["octene"], "3.9 18.7 13.2": ["simpleness"], "21.4 8.2 10.1": ["reorgs"], "8.6 9.4 9.7": ["lalu"], "2.5 21.1 10.9": ["abstentionism"], "-0.9 10.0 16.7": ["bittering"], "13.5 24.6 5.3": ["netherworlds"], "11.3 28.7 8.0": ["bodycount"], "12.0 9.4 32.7": ["tzimmes"], "19.1 9.1 18.7": ["junkfood"], "4.8 14.0 8.9": ["forementioned"], "0.8 7.9 6.7": ["parameterize"], "0.9 14.1 13.2": ["spladle"], "13.7 8.1 13.2": ["infrastructre"], "15.0 3.0 24.3": ["napery"], "-1.3 13.7 4.4": ["hairbrained"], "3.6 11.6 14.0": ["assort"], "17.8 10.7 13.6": ["snootful"], "25.7 -3.9 1.4": ["technlogy"], "10.6 12.7 19.1": ["trustafarian"], "13.5 9.7 9.0": ["resole"], "-12.5 14.9 -2.4": ["chall"], "10.4 12.9 12.4": ["tantalises"], "5.9 2.2 17.7": ["utang"], "16.0 -6.2 -3.9": ["seling"], "19.9 12.1 25.4": ["tribble"], "9.5 5.6 25.1": ["thatchers"], "7.0 -0.1 7.6": ["ronald"], "19.2 18.0 5.3": ["resilent"], "19.8 23.1 18.7": ["pestiferous"], "-8.6 7.2 7.8": ["redeterminations"], "12.9 1.0 -3.0": ["zl"], "23.3 11.2 22.7": ["scourer"], "-0.3 4.2 5.9": ["sensu"], "1.2 7.0 11.6": ["orthologous"], "10.9 12.1 33.8": ["bigos"], "14.4 1.8 10.9": ["unusuals"], "-4.3 14.3 4.2": ["capitally"], "12.1 20.3 2.7": ["utlimately"], "13.0 7.3 5.6": ["valveless"], "2.1 14.3 7.0": ["drillsites"], "4.2 -3.0 14.0": ["onlay"], "8.2 15.9 47.8": ["tunny"], "12.2 2.5 4.1": ["mountainboarding"], "8.0 8.2 11.4": ["colourised"], "14.0 8.1 17.0": ["zanily"], "9.1 15.3 5.0": ["atomizes"], "15.8 12.2 4.5": ["blogospheres"], "4.1 23.0 19.2": ["scarify"], "-0.9 -1.0 10.7": ["fiscalyear"], "15.7 19.6 6.7": ["coughers"], "10.7 18.7 9.2": ["peacful"], "9.1 -3.0 -1.9": ["terephthalate"], "4.2 7.3 14.7": ["mey"], "-0.0 17.1 -5.1": ["kabul"], "14.4 8.0 14.5": ["widly"], "9.3 11.4 38.3": ["viand"], "-10.3 1.0 9.2": ["rabba"], "12.9 8.7 14.4": ["arsenical"], "-5.9 28.1 0.5": ["executers"], "5.7 7.5 0.8": ["taoisigh"], "4.8 20.2 10.3": ["darfur"], "6.2 13.7 12.5": ["athero"], "12.0 12.6 22.5": ["chimeneas"], "18.1 13.5 21.5": ["purpled"], "11.3 10.1 21.6": ["caballeros"], "4.3 5.6 9.2": ["anoth"], "5.4 3.5 9.5": ["docosanol"], "9.6 11.0 7.7": ["granters"], "-2.6 -5.1 5.9": ["gyn"], "2.6 14.2 3.6": ["seinem"], "9.4 18.5 1.2": ["vitually"], "21.8 15.6 24.1": ["chequerboard"], "13.2 25.1 16.4": ["imagineable"], "13.5 13.8 14.7": ["berming"], "10.0 19.0 32.1": ["sternman"], "3.6 5.1 2.6": ["ihm"], "15.0 3.9 14.1": ["unemployables"], "9.4 5.7 24.5": ["koel"], "7.2 10.9 -1.1": ["hometowner"], "3.0 -3.0 2.1": ["anilox"], "6.8 0.2 -7.1": ["insitute"], "3.6 10.3 12.7": ["tenemos"], "18.2 13.5 6.9": ["xerographic"], "19.2 15.9 12.7": ["dicking"], "3.6 -5.4 9.7": ["endoprosthesis"], "1.3 4.6 16.3": ["padang"], "9.0 3.8 14.7": ["ouvert"], "10.8 -8.0 -1.5": ["sponors"], "-1.5 19.2 13.8": ["sprezzatura"], "-0.2 11.3 6.1": ["ilan"], "13.5 7.2 12.1": ["uncarpeted"], "14.8 1.1 4.2": ["electrospun"], "2.1 6.9 11.5": ["sulfamethoxazole"], "10.9 12.4 22.2": ["pardners"], "1.4 13.8 13.6": ["datus"], "13.2 -0.8 4.0": ["sountrack"], "15.8 5.3 36.6": ["mousaka"], "5.6 2.9 4.4": ["opthalmologists"], "3.6 1.9 3.9": ["mucoadhesive"], "-3.8 6.6 11.8": ["joanne"], "8.6 18.4 16.2": ["denny"], "10.6 7.3 10.2": ["staycationing"], "0.1 7.9 1.2": ["sadhvis"], "7.0 8.4 14.7": ["choix"], "12.3 -3.3 7.0": ["housecall"], "-2.3 22.0 7.5": ["tramatic"], "7.8 18.6 14.5": ["aag"], "0.9 14.5 -3.4": ["inists"], "9.3 9.1 12.5": ["anticlinal"], "12.0 1.5 13.0": ["curviest"], "-2.5 -6.3 3.9": ["outplaced"], "19.3 -0.5 8.7": ["pft"], "20.6 7.1 18.0": ["jobbie"], "0.2 4.5 3.7": ["aford"], "12.0 0.5 26.6": ["radiata"], "11.3 7.0 0.2": ["gprs"], "4.2 22.6 13.3": ["bwana"], "-1.5 -9.7 16.0": ["minigrant"], "-10.9 -5.4 4.9": ["urogynecologist"], "4.6 -0.6 8.1": ["sphygmomanometers"], "0.6 11.0 9.9": ["frenulum"], "14.8 6.7 45.4": ["kingklip"], "-6.5 13.8 17.6": ["leves"], "-1.2 4.3 4.0": ["nonmetastatic"], "-1.1 9.5 13.6": ["eles"], "6.2 7.8 6.6": ["contempory"], "4.4 24.0 13.5": ["predicatable"], "3.8 23.1 6.3": ["coersion"], "7.8 19.4 14.1": ["hackish"], "13.2 1.7 7.2": ["outsourcings"], "7.7 2.6 -2.5": ["thehigh"], "8.0 26.6 2.4": ["diplomacies"], "7.1 3.0 19.3": ["liveweights"], "14.3 0.5 0.3": ["nonmusic"], "5.6 5.5 9.1": ["carbenes"], "4.1 13.5 -0.5": ["sophomorically"], "6.2 9.0 14.4": ["sist"], "5.5 -2.2 1.7": ["keyboarder"], "-4.1 5.0 -6.5": ["televized"], "7.2 0.7 17.0": ["floc"], "6.9 -3.4 7.2": ["europea"], "-2.2 -4.4 6.1": ["trea"], "7.5 -0.6 17.5": ["nonrunners"], "-0.3 3.2 9.5": ["microdissection"], "7.9 29.1 2.1": ["backslidden"], "16.2 4.4 16.3": ["salto"], "-1.7 14.8 1.5": ["contradictive"], "11.3 3.7 10.8": ["stonker"], "12.2 25.8 16.8": ["sorceresses"], "-3.8 6.0 8.4": ["subprograms"], "4.2 -0.4 -6.4": ["outlicensed"], "-3.3 9.8 2.3": ["childeren"], "4.5 28.4 3.3": ["falsifiers"], "5.1 3.0 6.6": ["seconde"], "-2.6 10.6 -7.8": ["inisted"], "2.5 26.9 13.2": ["terp"], "10.0 5.7 20.3": ["passementerie"], "-2.7 15.5 12.8": ["imigration"], "1.0 3.6 6.5": ["lider"], "10.1 19.1 2.5": ["greates"], "-1.2 3.5 3.8": ["webform"], "22.1 16.8 16.9": ["dunnies"], "12.1 13.6 7.0": ["horsepowered"], "0.0 5.8 1.5": ["polynucleotide"], "13.9 21.3 11.5": ["rawly"], "15.2 15.0 24.9": ["trireme"], "3.6 9.9 7.5": ["sarai"], "8.0 11.4 9.9": ["effuse"], "2.7 3.9 7.0": ["bassoonists"], "18.7 11.0 7.7": ["gallic"], "1.8 9.1 6.5": ["plaing"], "12.0 20.2 6.0": ["outpunching"], "9.3 18.2 9.5": ["packhorses"], "5.4 9.2 1.5": ["datedness"], "2.0 8.1 3.5": ["allged"], "10.7 21.8 -2.8": ["overhasty"], "14.6 21.7 1.4": ["depressurised"], "5.7 9.8 11.8": ["glottis"], "-5.3 6.6 -0.3": ["concent"], "7.5 5.2 8.4": ["llegar"], "11.7 10.3 26.5": ["racemes"], "3.5 2.4 14.1": ["dira"], "-0.5 9.7 17.4": ["kilocalorie"], "16.2 -1.4 16.4": ["lotioned"], "8.4 10.6 22.7": ["amaranthus"], "16.2 14.0 27.4": ["splashers"], "7.9 10.5 2.7": ["videoblogging"], "2.1 20.7 12.9": ["stupefies"], "3.7 -1.8 13.2": ["sessioning"], "3.6 10.6 1.1": ["friendster"], "4.5 22.6 7.3": ["golpistas"], "8.8 0.0 -2.2": ["rearchitected"], "11.3 5.5 13.6": ["backscreen"], "4.4 17.3 5.3": ["promisee"], "6.0 3.9 6.1": ["allerdings"], "-6.4 4.8 6.4": ["andi"], "17.4 15.6 -1.4": ["oilwells"], "23.0 12.7 19.2": ["agribiz"], "-0.1 -1.3 4.4": ["pendancy"], "19.4 5.0 11.6": ["drawworks"], "7.7 12.7 10.2": ["garrulousness"], "13.1 7.6 2.9": ["musika"], "3.2 14.8 12.1": ["weedeaters"], "14.8 26.9 18.5": ["cryptids"], "9.9 12.8 11.8": ["htat"], "12.6 9.9 12.5": ["ehm"], "1.3 16.8 -4.7": ["constituional"], "6.7 2.5 -2.1": ["andinternational"], "9.6 14.1 12.6": ["ginga"], "8.1 3.1 11.5": ["eartags"], "2.4 2.1 5.6": ["acccident"], "4.0 10.6 15.3": ["meristem"], "4.2 9.0 15.0": ["manitoba"], "10.0 -2.2 10.2": ["ecotainer"], "20.7 2.5 31.3": ["handcut"], "-0.5 21.3 3.0": ["tapasya"], "10.0 19.6 5.8": ["revo"], "1.2 8.7 7.2": ["veri"], "12.0 16.3 1.5": ["developmentalism"], "2.6 -6.6 3.1": ["pubished"], "12.1 15.7 10.6": ["ovi"], "12.4 1.2 12.7": ["shishas"], "6.0 21.0 14.0": ["termiticide"], "15.0 12.5 18.5": ["matchy"], "28.4 16.7 31.6": ["mynah"], "-6.2 20.8 0.9": ["communalization"], "8.3 5.1 0.2": ["cardiograph"], "-1.2 16.6 -0.9": ["aknowledge"], "14.8 1.8 6.3": ["nafta"], "13.3 15.4 15.5": ["orderonlinecialis"], "3.2 11.5 4.3": ["toher"], "-8.5 6.3 -2.5": ["candidiate"], "5.8 16.5 15.0": ["nostalgist"], "16.0 16.0 10.2": ["rahodeb"], "5.0 10.1 18.8": ["propanolol"], "4.3 -8.3 6.9": ["biocomposites"], "-7.8 11.4 1.4": ["checkride"], "11.4 3.3 12.9": ["adieus"], "6.3 22.9 -2.2": ["asault"], "6.7 14.1 10.1": ["klansmen"], "11.3 1.6 22.0": ["undissolved"], "7.8 -1.5 19.1": ["festas"], "7.9 3.0 16.1": ["nolvadex"], "13.9 14.8 13.3": ["brachycephalic"], "-7.0 6.7 0.6": ["welcomerewards"], "7.1 16.2 17.2": ["lisped"], "9.8 9.1 22.3": ["tisane"], "3.8 -4.0 -5.9": ["bioprosthesis"], "4.8 1.1 4.1": ["maitre"], "6.1 13.0 6.0": ["siezure"], "14.7 26.4 18.3": ["widowmaker"], "18.0 4.8 4.9": ["coys"], "-6.6 3.4 -3.2": ["nonrated"], "14.4 12.2 24.4": ["icesheets"], "-0.9 21.0 4.8": ["cantonization"], "6.5 15.2 7.1": ["preclear"], "3.6 9.5 4.4": ["videographing"], "17.1 2.1 5.7": ["goldies"], "11.8 -3.2 -0.4": ["beschikbaar"], "10.0 9.3 37.0": ["parm"], "5.7 10.4 13.6": ["reflowed"], "18.9 17.3 8.9": ["crimebuster"], "14.5 7.2 8.4": ["aapl"], "2.8 -2.2 23.3": ["marin"], "-0.8 13.9 5.4": ["botho"], "15.5 1.4 5.1": ["spryly"], "0.1 4.9 16.6": ["tery"], "-0.1 -2.4 8.3": ["partcipants"], "0.5 4.5 0.3": ["hoff"], "11.0 5.9 10.1": ["fleapit"], "0.4 10.1 3.9": ["acquital"], "6.8 4.3 8.8": ["millsite"], "9.1 0.5 15.7": ["aries"], "10.7 10.5 15.5": ["microcavity"], "-3.5 16.6 5.0": ["solecisms"], "13.1 27.7 2.6": ["cybercommand"], "5.9 7.8 1.0": ["deatils"], "-0.8 4.4 20.6": ["kie"], "11.2 12.8 36.8": ["veligers"], "6.3 21.2 13.7": ["sre"], "3.5 -1.2 4.7": ["ayant"], "5.8 30.2 13.2": ["cruelness"], "3.1 6.9 13.8": ["kundiman"], "3.9 31.4 3.0": ["stalemating"], "4.9 7.5 1.6": ["mustbe"], "5.2 -4.7 1.6": ["presi"], "17.9 15.2 27.6": ["kelpies"], "26.0 -3.9 0.3": ["telecommuncations"], "1.4 0.7 7.8": ["ksi"], "13.7 18.7 11.9": ["microstate"], "1.3 10.3 15.8": ["possies"], "9.7 -6.9 -0.5": ["rushprnews"], "-2.8 -1.4 12.4": ["ketogenic"], "6.2 -2.3 -1.9": ["tereastarr"], "4.4 3.4 7.8": ["liqudity"], "14.6 9.0 6.0": ["avion"], "10.2 13.7 13.2": ["fourscore"], "19.2 8.2 15.6": ["bouyancy"], "17.1 7.4 32.8": ["meranti"], "0.8 -3.6 3.7": ["fnished"], "9.6 11.0 29.7": ["greenfinches"], "-5.6 13.1 6.6": ["apneic"], "12.6 -2.2 5.1": ["soughtafter"], "-7.3 -0.2 0.4": ["junor"], "8.7 18.3 11.7": ["gatka"], "7.4 8.3 3.3": ["comprend"], "14.3 24.5 12.9": ["telepaths"], "5.7 14.3 9.7": ["butalso"], "-0.7 6.2 10.1": ["partic"], "5.3 7.6 27.3": ["scalder"], "2.9 -13.4 -3.9": ["sumbitted"], "16.3 1.8 15.2": ["makea"], "1.4 7.7 35.6": ["sailfishing"], "9.8 11.1 -4.0": ["backshop"], "3.7 6.2 6.8": ["astrocytic"], "7.0 19.9 17.2": ["envenomation"], "-1.8 10.7 0.9": ["pseudorandom"], "-0.8 6.7 20.5": ["patay"], "-2.6 15.1 13.1": ["choosiness"], "-0.6 9.0 7.2": ["autopista"], "12.2 12.0 8.9": ["facer"], "-0.2 5.4 6.4": ["bli"], "-5.3 6.5 3.4": ["unmethylated"], "6.1 8.6 15.2": ["paddywagon"], "15.9 13.4 5.5": ["pastings"], "8.2 8.5 11.6": ["rondavels"], "4.9 17.0 21.3": ["crossable"], "7.1 19.5 6.8": ["unintelligently"], "-3.2 10.2 9.7": ["semaphorin"], "12.7 9.0 7.6": ["oogling"], "18.2 15.4 -4.8": ["revolutionalised"], "-5.5 8.2 0.0": ["ajc"], "17.5 18.6 19.1": ["glooming"], "-0.0 28.2 4.6": ["racialists"], "3.3 8.4 10.4": ["cyclicity"], "8.9 2.7 13.5": ["parkside"], "14.4 12.9 9.1": ["finall"], "10.8 3.8 9.3": ["preparty"], "14.3 18.4 8.1": ["testfired"], "13.5 9.1 8.5": ["satyam"], "-5.4 7.6 6.8": ["parampara"], "-2.8 28.0 8.0": ["retasked"], "8.6 17.3 16.5": ["totipotent"], "1.0 20.3 7.5": ["midcarder"], "6.4 5.8 9.3": ["bankless"], "3.8 13.0 11.5": ["thelemurking"], "-2.8 7.8 2.0": ["nomograms"], "0.3 13.6 8.2": ["phosphodiesterases"], "0.9 6.3 9.8": ["uska"], "7.6 8.0 14.0": ["trustafarians"], "-0.2 15.3 13.0": ["watchstander"], "3.2 13.5 7.1": ["paleoclimatologists"], "7.8 2.7 8.9": ["firelog"], "20.2 16.5 39.0": ["senkos"], "7.9 5.3 15.7": ["wadas"], "10.4 12.7 9.7": ["hypergrid"], "8.0 -0.4 3.7": ["distibution"], "10.0 16.5 12.0": ["scenary"], "9.6 13.8 7.2": ["unionising"], "9.4 18.5 19.2": ["bobtailing"], "14.6 6.2 21.1": ["bambinos"], "21.2 8.5 33.7": ["frizzle"], "10.2 15.2 7.8": ["iminent"], "9.9 17.9 7.4": ["aspirationals"], "4.5 14.6 2.3": ["disbalance"], "4.0 8.6 -0.7": ["regionalising"], "9.9 17.2 27.5": ["chanteys"], "-2.1 43.2 2.6": ["anticoalition"], "12.2 10.9 1.4": ["presidencial"], "14.1 10.4 20.2": ["pommy"], "4.8 14.0 11.0": ["wreathing"], "1.7 6.6 3.6": ["offficial"], "3.7 -2.5 11.6": ["glucocorticosteroid"], "0.7 15.1 -0.3": ["canonizes"], "-1.3 5.7 11.8": ["maza"], "-2.8 -3.9 8.1": ["winnners"], "2.3 18.8 9.8": ["downconvert"], "3.0 10.7 29.1": ["tira"], "3.3 6.2 4.4": ["adsorptive"], "2.4 -4.1 5.6": ["elure"], "-4.8 3.6 6.8": ["reauthorisation"], "5.4 2.0 2.9": ["quadricycles"], "6.2 -3.1 8.4": ["backport"], "11.8 0.3 19.4": ["zhen"], "-1.3 7.7 7.4": ["enoximone"], "9.7 51.2 11.2": ["respawned"], "-0.6 14.9 10.5": ["literals"], "17.3 24.0 12.9": ["firebreathing"], "7.0 12.1 23.9": ["onna"], "8.9 -7.1 2.5": ["ervice"], "11.9 12.7 10.6": ["androgyne"], "-2.1 12.3 4.7": ["ult"], "-2.4 9.2 9.1": ["primidone"], "10.5 15.9 12.6": ["dopeheads"], "8.3 10.1 9.5": ["musicianly"], "2.2 1.5 -8.1": ["ftm"], "7.6 16.6 15.7": ["demarking"], "-0.2 9.1 3.2": ["warum"], "3.3 12.4 10.9": ["haley"], "6.6 8.7 11.3": ["ajay"], "-0.5 -9.1 16.4": ["afa"], "-10.3 5.8 12.7": ["jaga"], "8.6 11.0 31.9": ["whitetip"], "8.4 5.2 4.7": ["buidlings"], "1.2 5.8 8.5": ["ofthat"], "9.4 21.8 15.1": ["uneccessary"], "12.7 7.7 18.9": ["cloverleafs"], "1.0 13.7 30.1": ["intercoastal"], "3.3 13.0 1.7": ["lahore"], "9.6 -1.2 7.7": ["resultados"], "13.2 -1.6 12.5": ["lacto"], "7.7 11.9 9.7": ["famillies"], "4.2 15.4 8.9": ["usuable"], "14.4 9.7 18.6": ["paralle"], "6.6 12.1 28.0": ["bearberry"], "-1.5 1.8 -0.4": ["toolchains"], "7.4 14.5 4.1": ["antedates"], "-3.0 2.7 5.7": ["sunil"], "0.1 13.1 11.6": ["negara"], "-0.7 -8.7 9.1": ["postgrads"], "-1.3 4.9 14.6": ["fisetin"], "2.2 8.1 5.4": ["ecclesia"], "12.0 1.8 16.8": ["papillons"], "1.4 6.3 6.6": ["remian"], "3.0 13.7 2.8": ["immunotoxin"], "4.5 15.2 7.2": ["powerbases"], "13.4 15.8 6.3": ["spycams"], "7.0 9.8 -0.2": ["superusers"], "12.8 2.3 5.2": ["photobiology"], "-3.2 20.4 4.3": ["clerisy"], "12.8 24.6 11.2": ["declinist"], "5.6 3.4 3.7": ["sinuplasty"], "2.7 6.0 5.0": ["thatcan"], "13.9 10.6 14.1": ["enthrallingly"], "17.7 12.3 37.4": ["anhingas"], "14.4 -1.3 2.7": ["deathknell"], "9.4 14.3 8.8": ["chems"], "26.1 10.2 24.2": ["beefeater"], "-5.7 -7.1 6.6": ["tioned"], "13.8 8.4 41.0": ["redhorse"], "8.1 6.0 5.0": ["revivification"], "-4.5 25.5 11.8": ["homegrowns"], "19.6 11.6 19.4": ["hookless"], "14.0 3.5 34.5": ["marscapone"], "5.9 13.8 10.0": ["absoutely"], "0.9 24.6 5.4": ["kasab"], "7.3 16.7 15.1": ["letoff"], "-2.6 4.5 16.1": ["muertos"], "7.7 0.9 0.4": ["onthis"], "0.2 29.3 2.2": ["seperatists"], "7.1 6.6 8.4": ["bluecollar"], "15.3 4.4 6.0": ["doubleclick"], "-7.1 -0.8 1.4": ["esh"], "4.6 27.7 12.6": ["radoks"], "0.9 5.6 6.1": ["confrimed"], "-5.0 3.2 21.7": ["tamang"], "24.9 19.8 26.7": ["ribcages"], "7.5 8.7 5.3": ["wans"], "6.5 11.3 2.9": ["fluorodeoxyglucose"], "27.1 7.1 30.0": ["strawflower"], "4.6 16.5 2.9": ["contendor"], "11.6 -2.2 14.8": ["ieee"], "7.4 9.6 8.2": ["economys"], "7.3 12.1 0.9": ["degausser"], "-11.1 11.7 2.9": ["tafsir"], "6.1 3.0 19.0": ["rawa"], "12.6 21.8 7.2": ["neighours"], "4.8 18.9 10.4": ["movielike"], "3.3 4.4 5.5": ["enourage"], "5.3 1.6 5.2": ["finanacial"], "6.0 17.4 4.0": ["confabulated"], "10.9 19.7 13.2": ["abidingly"], "2.6 6.5 -2.6": ["chie"], "13.0 -1.0 27.8": ["poultrymeat"], "-0.7 18.6 9.6": ["shastras"], "0.4 7.6 4.4": ["ganization"], "-2.8 20.9 8.7": ["leftys"], "20.8 13.6 33.5": ["juiceless"], "16.3 18.6 14.4": ["rockchalk"], "2.8 11.6 15.7": ["usi"], "7.2 2.1 13.7": ["barnets"], "4.6 16.3 7.0": ["polce"], "8.1 4.6 17.6": ["opaques"], "7.0 -0.2 -5.5": ["mathaba"], "11.7 11.7 11.7": ["peeple"], "12.6 15.8 21.8": ["taiaha"], "3.3 17.1 3.5": ["asume"], "3.9 0.4 14.4": ["ethanolamine"], "1.8 8.6 -0.3": ["ideating"], "7.1 3.3 5.7": ["mismangement"], "-4.0 12.4 -1.3": ["nobrainer"], "20.4 13.5 18.0": ["pharoahs"], "6.1 0.7 -8.1": ["electrocardiographs"], "11.2 20.4 6.6": ["identiy"], "13.4 21.7 6.8": ["eeeevil"], "-4.3 0.4 5.5": ["thirrd"], "13.9 5.5 6.2": ["ealy"], "-0.0 12.4 15.2": ["capsaicinoids"], "8.9 29.2 16.2": ["camos"], "-0.1 9.0 3.4": ["enure"], "19.1 21.3 20.3": ["forefeet"], "15.4 6.9 30.3": ["pitaya"], "-5.1 7.2 9.3": ["otitis"], "19.9 8.9 45.3": ["panfried"], "9.9 11.3 42.1": ["checkerspot"], "8.0 2.8 5.8": ["bubbliest"], "-7.3 2.3 2.5": ["orofacial"], "6.4 7.7 14.6": ["overshirt"], "24.8 19.6 15.8": ["mantrap"], "6.7 8.8 12.5": ["kalikasan"], "7.3 15.6 11.3": ["ohmigod"], "7.4 7.1 10.0": ["frontfoot"], "14.5 1.9 -0.4": ["vcr"], "-1.1 3.3 8.6": ["vecuronium"], "17.1 4.0 10.9": ["truckish"], "-0.6 9.8 8.1": ["asher"], "-4.1 -0.5 8.4": ["questionmarks"], "8.5 7.9 5.6": ["philharmonics"], "-0.1 6.9 20.0": ["kaagad"], "8.0 17.5 39.1": ["redears"], "0.2 11.3 3.1": ["nonreligion"], "4.9 24.1 4.4": ["relativize"], "10.9 30.1 19.0": ["bushies"], "6.0 26.7 1.6": ["hegemonist"], "-1.8 9.4 12.6": ["adduct"], "3.5 13.1 9.8": ["misallocate"], "9.5 12.3 13.5": ["neville"], "11.6 30.8 1.3": ["lynchers"], "10.4 6.2 -0.6": ["spigit"], "-1.1 7.7 10.4": ["yayas"], "-9.7 0.5 5.6": ["epididymitis"], "10.1 -0.3 17.5": ["escudos"], "6.7 3.4 3.9": ["parasiticides"], "9.7 5.9 34.6": ["pinakbet"], "7.4 13.9 -2.4": ["brainstrust"], "2.9 3.2 13.7": ["pedestrianism"], "6.9 6.6 7.6": ["copenhagen"], "5.9 6.3 17.6": ["alata"], "18.3 8.5 25.0": ["gundogs"], "15.8 18.2 4.2": ["archetypically"], "15.6 7.1 9.2": ["walgreens"], "8.2 10.0 2.3": ["incured"], "6.6 1.1 3.0": ["clavier"], "11.6 -1.7 10.2": ["grasstrack"], "19.0 13.7 24.1": ["caryatids"], "5.0 4.3 7.6": ["bith"], "19.8 6.6 11.6": ["exercycle"], "-0.3 13.8 7.6": ["inall"], "1.0 12.9 4.0": ["perse"], "-5.3 6.8 6.0": ["bedouns"], "2.0 -5.8 10.0": ["hayland"], "8.3 10.1 23.4": ["pok"], "5.0 1.5 12.9": ["paperbound"], "19.0 15.2 18.4": ["thunderbirds"], "8.8 -1.0 1.1": ["haircutters"], "11.3 13.0 14.4": ["telangiectasia"], "3.6 -0.6 9.0": ["isradipine"], "25.4 12.1 31.8": ["cueball"], "14.7 14.6 23.7": ["redbirds"], "9.2 7.5 14.1": ["polyunsat"], "-4.4 11.6 2.2": ["dismissable"], "12.5 23.9 5.8": ["intelligensia"], "-2.1 6.8 6.2": ["mant"], "-5.7 0.7 1.0": ["certolizumab"], "10.2 2.5 11.6": ["musi"], "4.8 21.7 8.3": ["misprison"], "14.0 4.8 12.4": ["benefication"], "10.5 14.6 36.5": ["redbreast"], "20.2 13.6 30.7": ["guck"], "0.3 -0.5 3.5": ["antiapoptotic"], "-2.9 4.9 2.6": ["educaiton"], "8.4 4.2 23.8": ["antojitos"], "20.0 7.2 18.5": ["clopped"], "6.5 12.1 5.6": ["ancestory"], "1.3 17.1 1.8": ["chummily"], "0.9 -0.8 1.6": ["schoolgoing"], "20.5 3.9 14.3": ["tophat"], "17.4 1.6 13.5": ["multilocation"], "1.2 3.3 8.5": ["chancroid"], "12.1 15.6 13.8": ["whackiest"], "8.7 23.7 7.1": ["charachter"], "10.0 14.1 25.4": ["callosities"], "0.8 8.1 6.1": ["dorsolateral"], "2.6 5.6 15.8": ["vicki"], "-1.4 15.8 7.4": ["unperfected"], "-0.7 4.0 4.4": ["inolved"], "-4.9 4.2 15.2": ["wakesurfing"], "-3.8 0.8 3.8": ["metting"], "6.3 -1.5 8.1": ["utf"], "-13.6 2.6 -1.1": ["subscores"], "6.5 25.6 24.8": ["medusahead"], "4.2 -6.1 4.2": ["halfof"], "2.7 10.8 10.4": ["valo"], "8.1 7.9 8.3": ["romancers"], "8.1 4.6 15.8": ["terriffic"], "4.2 7.5 6.3": ["trackbed"], "14.7 0.2 5.5": ["aftre"], "8.8 7.8 12.6": ["farecards"], "23.5 11.4 15.0": ["ahuge"], "12.8 5.7 5.8": ["sqeeze"], "18.2 9.4 40.2": ["vinegared"], "8.2 11.9 2.5": ["uncodified"], "-2.0 5.9 16.5": ["taan"], "12.7 6.3 4.7": ["ringtunes"], "11.7 21.4 16.2": ["pressu"], "-2.1 1.2 7.3": ["rehearings"], "4.9 14.3 15.3": ["bitchily"], "19.9 8.8 7.3": ["spivvy"], "22.5 12.0 16.3": ["baloons"], "5.6 17.0 13.1": ["slickuser"], "12.9 25.9 12.0": ["vitalism"], "4.7 9.5 8.4": ["relinking"], "6.8 6.0 25.3": ["carinderia"], "-2.6 6.6 6.3": ["carotids"], "4.0 6.6 14.4": ["midlevels"], "10.2 11.8 10.5": ["sludged"], "4.4 18.7 12.5": ["pathan"], "4.0 18.4 -4.2": ["shoebomber"], "8.6 6.5 15.2": ["nibh"], "21.7 8.5 25.7": ["nailheads"], "5.6 8.7 10.6": ["insolated"], "4.0 8.9 13.8": ["villous"], "6.7 7.5 10.8": ["geobiology"], "25.3 7.4 47.9": ["crustacea"], "-4.4 15.0 10.2": ["chromosomally"], "6.6 -0.4 9.7": ["avandia"], "1.9 11.4 8.5": ["soundoff"], "16.4 10.3 4.5": ["wmf"], "19.4 9.1 28.8": ["luffa"], "9.4 7.2 13.3": ["mistily"], "2.0 1.4 12.4": ["evian"], "12.8 6.4 23.8": ["glauca"], "6.1 2.8 -5.2": ["puruse"], "16.5 8.3 15.3": ["superstretch"], "18.4 27.5 15.0": ["lightnings"], "24.8 24.8 15.8": ["vulcan"], "4.0 -2.9 12.2": ["chessfest"], "8.8 17.0 12.2": ["deffo"], "-1.8 5.8 5.2": ["custoday"], "-3.8 8.6 5.7": ["aleatoric"], "19.3 6.1 10.0": ["corkboards"], "-0.0 -1.1 12.8": ["kilowatthour"], "8.3 7.0 15.8": ["balmiest"], "-2.1 18.2 2.9": ["checkings"], "10.8 2.7 17.1": ["pkgs"], "7.6 10.1 2.4": ["throuh"], "1.0 6.5 7.1": ["phosphatidylinositol"], "3.6 31.0 2.3": ["singlemindedness"], "13.4 11.8 13.9": ["strake"], "17.6 16.3 24.7": ["dumbell"], "-7.1 14.9 4.4": ["strengthed"], "14.3 27.0 22.8": ["shotted"], "-0.6 7.7 10.8": ["panleukopenia"], "5.0 9.9 6.6": ["hyperfine"], "17.4 3.1 3.7": ["collasped"], "11.8 20.5 20.0": ["motionlessly"], "1.0 -0.5 19.7": ["enological"], "21.9 11.1 22.5": ["orgasmically"], "-0.3 9.3 4.6": ["laywomen"], "0.9 7.2 9.8": ["nritta"], "-2.0 5.2 6.8": ["verteporfin"], "4.9 4.0 10.8": ["brin"], "6.1 7.7 5.7": ["ecu"], "3.9 16.9 -1.1": ["uknown"], "4.0 25.3 12.1": ["eachothers"], "8.3 3.9 7.1": ["harlem"], "-4.2 4.5 10.8": ["dispositioned"], "19.4 14.8 22.3": ["rimrock"], "1.7 4.7 10.3": ["escheatment"], "-8.3 2.0 8.7": ["incrementals"], "12.6 14.3 1.4": ["disolve"], "9.0 4.2 18.8": ["phyllites"], "7.0 -2.5 8.8": ["rollerbladed"], "10.6 13.2 3.8": ["afterimages"], "6.6 9.2 -6.7": ["newssite"], "11.0 11.7 14.5": ["defog"], "12.7 21.0 0.1": ["unbeholden"], "-0.8 6.3 10.9": ["semua"], "3.2 11.8 7.4": ["aphorist"], "13.2 21.4 8.2": ["outpower"], "4.9 2.1 1.5": ["jestingly"], "2.5 -3.6 2.0": ["eurokiwi"], "2.8 1.9 15.5": ["girlier"], "4.2 11.9 11.1": ["frontwomen"], "9.8 0.5 5.8": ["beso"], "11.1 3.9 17.2": ["hindlimbs"], "-8.6 -1.4 4.5": ["interterm"], "8.3 23.9 11.5": ["outman"], "12.2 3.1 17.6": ["degus"], "15.3 11.8 6.5": ["daubings"], "10.5 3.8 9.8": ["glucokinase"], "0.3 12.0 16.1": ["bangsa"], "10.6 3.3 13.6": ["receeded"], "3.5 17.3 3.0": ["reverred"], "8.4 5.9 9.3": ["madoff"], "3.6 5.8 3.5": ["pointscorer"], "11.9 16.3 6.6": ["orrible"], "5.2 4.5 8.0": ["chitchats"], "9.5 12.7 11.9": ["halfcentury"], "5.9 25.6 10.1": ["microexpressions"], "3.5 2.6 0.6": ["colette"], "21.1 9.4 8.8": ["pumpjack"], "10.9 15.5 43.8": ["bluebill"], "0.6 20.9 13.6": ["trichotomy"], "13.8 1.2 10.2": ["boilerhouse"], "15.0 19.5 14.1": ["minifigures"], "-3.1 8.8 2.7": ["qualifyings"], "-7.9 12.1 -3.2": ["disendorse"], "11.6 4.6 26.3": ["reubens"], "6.7 24.9 6.2": ["personalistic"], "8.5 8.0 17.9": ["motte"], "14.8 4.5 8.2": ["lue"], "0.2 19.0 4.2": ["rimes"], "-2.7 -1.0 6.2": ["jobseeking"], "11.8 -0.2 12.8": ["bost"], "0.4 10.7 8.4": ["archaically"], "12.7 17.5 17.3": ["epaulette"], "6.3 12.8 21.1": ["waterskier"], "3.1 9.1 16.1": ["medigap"], "4.5 -0.1 8.2": ["ionomer"], "6.5 35.3 0.5": ["millitants"], "17.9 12.0 8.6": ["backback"], "-2.7 -0.0 2.1": ["schizoaffective"], "7.5 -9.6 6.4": ["commer"], "6.8 13.0 18.8": ["perforator"], "15.1 17.7 14.1": ["meeja"], "8.9 -1.3 -0.2": ["secondee"], "3.3 10.8 14.1": ["cuttable"], "4.2 18.9 13.4": ["underexpose"], "5.6 10.7 13.2": ["cryovolcanism"], "15.6 -2.4 7.9": ["trillon"], "9.2 1.6 6.4": ["productdevelopment"], "-0.0 1.2 17.1": ["pareho"], "8.3 26.0 16.7": ["cannonading"], "4.2 13.5 2.2": ["hyperinflations"], "9.9 10.3 5.6": ["boundaryless"], "8.1 8.8 28.4": ["fishpens"], "13.6 21.8 10.3": ["crimebusters"], "1.7 10.2 10.3": ["dipeptide"], "16.5 4.5 13.3": ["plein"], "5.5 13.8 4.2": ["scission"], "19.1 10.1 12.8": ["clangy"], "18.6 4.3 21.6": ["nyala"], "7.6 2.0 4.4": ["scandle"], "5.2 17.4 8.1": ["entraining"], "1.1 16.8 -1.2": ["salesy"], "7.5 -6.3 10.6": ["sqf"], "-1.7 11.5 2.6": ["phonorecords"], "16.7 11.6 44.1": ["chokka"], "8.6 15.9 16.6": ["parthenium"], "15.0 23.4 8.4": ["irately"], "1.8 10.7 9.6": ["cockeril"], "3.0 6.5 7.0": ["especiallly"], "2.9 9.2 22.0": ["timecharter"], "3.4 -2.7 16.4": ["martes"], "1.3 6.2 10.2": ["orbitofrontal"], "10.2 32.7 12.4": ["outselves"], "13.5 7.1 26.7": ["nigella"], "4.4 6.0 6.8": ["tivity"], "26.2 11.9 26.1": ["banyans"], "13.4 9.0 33.8": ["motorboating"], "10.0 7.0 17.6": ["noize"], "12.9 21.2 12.1": ["oneupsmanship"], "-2.3 11.4 17.2": ["allocative"], "7.4 12.1 4.9": ["probalby"], "1.0 9.8 9.1": ["escheated"], "13.9 6.8 15.5": ["waterball"], "13.1 10.1 5.9": ["turbulently"], "4.3 -6.4 2.7": ["damas"], "18.6 16.7 8.9": ["stratospheres"], "14.6 5.4 13.2": ["ciel"], "14.2 10.8 27.2": ["chamfers"], "2.8 10.1 9.3": ["yom"], "11.2 15.4 20.9": ["orientals"], "10.1 18.1 3.2": ["crawlable"], "13.1 2.0 5.2": ["cartoner"], "11.0 8.3 9.3": ["defoamers"], "6.4 10.3 22.4": ["hev"], "18.0 14.4 14.6": ["kaleidoscopically"], "6.2 4.3 -0.2": ["antianxiety"], "2.6 7.3 12.6": ["azoxystrobin"], "7.8 15.0 9.3": ["inputing"], "13.5 6.3 12.2": ["stalest"], "-6.4 3.4 1.2": ["ruxolitinib"], "6.0 11.4 10.3": ["eppin"], "-1.5 5.9 0.9": ["daugter"], "14.4 8.4 6.7": ["underpromising"], "16.6 4.2 38.6": ["pepperoncinis"], "6.8 8.7 19.5": ["becky"], "-3.9 5.2 6.7": ["aggrivated"], "21.3 2.7 33.5": ["appetizingly"], "6.4 2.3 33.5": ["hanwoo"], "4.5 0.9 7.3": ["mihn"], "7.1 1.5 -0.8": ["promis"], "-0.3 16.0 10.9": ["mabey"], "29.5 11.8 30.5": ["gobstopper"], "7.6 18.7 0.9": ["wormable"], "9.5 15.6 17.5": ["graphane"], "-2.4 6.6 6.0": ["scp"], "4.8 2.2 1.8": ["lactamase"], "11.5 4.3 4.0": ["gotton"], "0.4 3.3 11.0": ["seasson"], "9.3 20.0 17.2": ["lairds"], "7.1 24.8 1.7": ["commandante"], "13.7 0.3 2.0": ["pric"], "7.2 6.7 4.6": ["chorals"], "2.8 -0.1 12.9": ["theproperty"], "3.7 8.9 14.3": ["stackability"], "11.2 4.8 12.2": ["antiwrinkle"], "9.9 16.0 -1.3": ["calimed"], "4.5 21.7 14.3": ["unnaturalness"], "11.5 5.3 9.1": ["scandale"], "18.8 -0.4 1.6": ["homeshopping"], "2.7 4.9 6.4": ["morphometry"], "8.7 11.0 22.7": ["octopamine"], "3.3 0.5 12.1": ["dentifrice"], "14.1 2.9 27.2": ["livermush"], "1.7 16.6 5.5": ["synchronic"], "13.4 2.1 26.4": ["pechay"], "1.5 4.4 6.6": ["paz"], "9.1 8.6 25.8": ["gunnysacks"], "3.2 9.4 -0.4": ["extorsion"], "4.5 10.5 1.5": ["defragged"], "9.4 2.2 16.2": ["supermarts"], "6.3 13.9 12.5": ["firangi"], "3.1 1.7 8.2": ["monos"], "14.3 16.1 11.9": ["speciesist"], "8.4 22.5 7.0": ["compitition"], "12.2 14.0 16.2": ["sorries"], "6.8 -0.2 1.4": ["bullfrogpowered"], "8.6 10.2 6.2": ["intuitional"], "4.2 9.5 5.8": ["helt"], "0.3 -7.2 -0.2": ["rdup"], "12.9 5.8 8.4": ["revheads"], "10.2 13.9 15.1": ["specta"], "2.7 0.9 4.9": ["sterilants"], "25.3 24.2 9.2": ["galactically"], "1.2 20.5 7.9": ["chastisements"], "1.0 9.2 5.8": ["jedoch"], "3.4 10.9 12.4": ["provence"], "16.0 5.7 10.1": ["underhyped"], "17.5 16.0 19.8": ["teensiest"], "-2.3 1.9 5.9": ["mcs"], "2.6 2.3 16.5": ["doub"], "9.8 16.2 12.0": ["wewere"], "-3.5 5.9 25.1": ["obon"], "1.8 5.0 10.3": ["beginnig"], "6.3 21.4 13.3": ["hooches"], "-1.1 8.2 10.6": ["interpretively"], "-0.4 10.4 13.6": ["raaga", "utilisable"], "9.2 25.6 8.3": ["heroe"], "10.5 5.1 1.8": ["uploadable"], "3.8 14.0 11.3": ["raveling"], "21.5 16.1 29.1": ["holdfast"], "17.4 16.6 24.0": ["unbranched"], "0.3 7.9 -5.1": ["superserve"], "20.7 14.1 18.8": ["stickless"], "6.1 9.7 12.5": ["selectin"], "4.6 18.7 11.6": ["athleted"], "8.1 7.6 8.9": ["secu"], "15.7 21.2 24.0": ["cryptozoologists"], "-1.0 6.2 12.9": ["newsflashes"], "7.1 9.7 17.2": ["fjb"], "5.9 6.6 7.2": ["outgas"], "11.9 1.5 7.8": ["srs"], "3.0 4.1 -0.9": ["opportunityto"], "9.2 13.1 12.5": ["orpg"], "21.6 20.3 32.0": ["fantails"], "-8.8 3.9 11.3": ["flavones"], "2.5 11.3 7.7": ["nonfilers"], "8.1 6.2 -3.2": ["defe"], "9.5 24.3 12.5": ["grinningly"], "0.9 21.6 10.2": ["diffent"], "20.7 10.1 17.1": ["jogo"], "6.6 3.1 8.0": ["toppermost"], "12.3 0.1 17.7": ["florence"], "7.4 10.6 3.8": ["autodialing"], "6.9 1.4 20.0": ["lehnga"], "9.2 14.8 3.9": ["autodial"], "13.6 16.7 6.2": ["collinear"], "1.3 15.4 18.0": ["midcarders"], "12.5 9.3 7.5": ["wheelarch"], "-8.6 3.3 6.8": ["nitrofurantoin"], "3.3 7.4 12.1": ["washables"], "9.0 3.7 5.5": ["dict"], "-2.6 1.9 -4.0": ["angiographies"], "12.4 11.4 0.8": ["ascendence"], "-12.5 3.4 3.2": ["disincorporated"], "5.6 -4.7 -0.7": ["newslink"], "10.1 0.1 14.1": ["modelesque"], "16.6 4.6 1.3": ["componentised"], "14.2 14.7 14.3": ["beered"], "0.5 4.2 8.8": ["workplans"], "8.4 14.2 10.3": ["pricelessly"], "3.9 17.6 1.3": ["fractioning"], "12.3 5.5 33.5": ["picanha"], "1.9 4.6 12.0": ["suzanne"], "1.2 7.0 2.6": ["goalshooter"], "-5.6 0.4 15.1": ["dnr"], "4.3 26.8 2.7": ["perpertrators"], "24.1 8.8 36.3": ["canteloupe"], "3.3 1.3 2.8": ["astate"], "-3.6 3.0 1.7": ["elling"], "3.0 7.3 8.6": ["assualting"], "15.5 12.6 22.7": ["unisexual"], "11.3 16.3 3.0": ["glanceable"], "3.9 -5.5 19.1": ["dandia"], "6.9 6.5 -1.0": ["torunament"], "3.6 9.2 15.4": ["finacee"], "20.4 4.0 22.2": ["hucked"], "13.9 8.0 31.2": ["glaucous"], "8.8 9.0 8.9": ["nyah"], "-1.4 9.1 0.6": ["montre"], "13.2 6.0 12.4": ["blotching"], "7.6 19.7 17.7": ["unassimilable"], "4.4 8.5 4.5": ["slackerdom"], "1.6 45.0 4.5": ["terorist"], "3.9 1.7 8.1": ["paycard"], "-1.3 14.7 15.3": ["ganguly"], "-5.1 29.8 5.4": ["predjudice"], "12.2 6.8 17.3": ["interplanted"], "-1.0 1.7 8.7": ["tona"], "-0.4 17.7 9.2": ["backdooring"], "0.6 17.8 5.8": ["penaly"], "11.3 21.5 11.7": ["polititions"], "20.8 5.7 18.6": ["gimcracks"], "10.5 16.7 5.1": ["vulnerabilties"], "18.8 12.8 15.5": ["razzi"], "7.0 7.5 14.4": ["tapis"], "10.3 16.4 5.5": ["rousers"], "4.8 13.1 3.1": ["picturization"], "0.8 15.1 4.2": ["unpenalised"], "7.9 18.4 6.6": ["vetern"], "12.7 2.9 20.7": ["ropa"], "6.0 13.7 8.8": ["uncoolness"], "4.2 -2.9 3.1": ["cablecasts"], "-2.1 9.0 9.3": ["discerningly"], "6.9 16.2 9.3": ["plist"], "3.1 4.4 4.6": ["werde"], "11.1 11.9 10.2": ["interferogram"], "9.5 0.8 0.9": ["shunter"], "11.4 16.2 5.8": ["blackwash"], "-4.3 15.1 5.6": ["galectin"], "10.8 13.1 21.3": ["coles"], "15.1 11.8 9.2": ["abrazo"], "1.3 23.4 9.6": ["ineloquent"], "5.9 16.2 2.1": ["definiton"], "8.7 8.2 7.7": ["superbantamweight"], "8.0 20.4 3.7": ["feudalists"], "14.5 12.4 1.7": ["hotsync"], "3.8 10.7 10.1": ["unpersuasively"], "1.9 13.4 29.6": ["localvores"], "2.9 1.0 8.8": ["cermonies"], "12.4 12.3 6.2": ["imagineer"], "11.3 -7.0 1.3": ["millones"], "10.7 10.5 4.2": ["startpage"], "3.3 10.4 9.2": ["welcher"], "3.4 9.3 3.1": ["stridor"], "5.5 7.2 12.9": ["capsulotomy"], "4.0 -1.5 4.9": ["morefocus"], "3.8 13.2 5.1": ["bazza"], "15.4 7.1 16.0": ["supersexy"], "7.1 7.9 8.5": ["nanomesh"], "-6.8 -1.8 5.2": ["frataxin"], "13.8 24.1 3.2": ["misleader"], "12.1 9.6 7.4": ["strengtheners"], "1.5 -4.8 8.4": ["iles"], "2.0 5.3 7.7": ["injuredreserve"], "11.6 14.1 16.0": ["obesogenic"], "14.1 3.2 -1.6": ["giffgaff"], "-5.1 12.8 16.6": ["jod"], "0.8 18.0 5.1": ["ultraorthodox"], "4.4 7.8 4.2": ["colorimeters"], "2.9 9.4 10.6": ["sangre"], "4.2 6.9 12.5": ["dunite"], "-13.5 7.3 -0.1": ["sisted"], "10.3 13.3 14.0": ["wholely"], "-0.2 9.6 21.2": ["paintballer"], "10.5 33.1 10.7": ["youare"], "4.5 6.3 0.1": ["coercivity"], "8.3 9.6 8.1": ["symantec"], "15.9 -7.2 6.0": ["prodcution"], "-4.8 2.4 0.8": ["addin"], "18.2 -2.1 34.0": ["yuba"], "13.9 1.2 22.3": ["oobleck"], "9.6 12.6 18.9": ["pocks"], "5.0 6.6 11.2": ["prs"], "2.7 4.4 8.0": ["varistor"], "6.5 8.2 14.0": ["clipless"], "5.7 18.0 7.6": ["pagefile"], "21.5 7.7 18.1": ["wallride"], "12.1 13.8 28.3": ["wienerschnitzel"], "-4.2 -6.0 27.0": ["churi"], "10.2 -5.4 -1.1": ["myclimate"], "13.5 16.2 11.1": ["intumescent"], "13.2 0.4 17.1": ["bioacoustics"], "15.4 11.1 28.8": ["poppadom"], "-3.6 16.2 0.3": ["sufism"], "-2.5 6.9 16.0": ["beachgoing"], "17.0 23.2 15.6": ["verminous"], "17.3 9.9 4.4": ["supersleuth"], "2.8 -3.1 3.7": ["appe"], "20.1 16.1 19.3": ["mortifyingly"], "2.5 11.1 10.2": ["caveolae"], "5.4 20.2 13.5": ["lawabiding"], "1.3 -9.9 2.3": ["coh"], "-0.5 27.4 9.5": ["themseves"], "7.4 1.8 5.3": ["aprt"], "15.0 17.5 12.5": ["exultations"], "3.7 7.7 5.8": ["teleserials"], "0.5 14.9 1.1": ["feministic"], "4.8 2.8 2.2": ["becames"], "2.6 1.6 1.8": ["antisepsis"], "8.0 9.7 5.4": ["siloxanes"], "-4.9 -3.0 4.3": ["arrainged"], "-3.4 7.6 5.6": ["rahi"], "10.2 6.0 11.8": ["longwalls"], "7.6 14.3 -0.6": ["infuence"], "-9.5 10.5 1.4": ["epeeists"], "-6.3 15.1 9.4": ["spiritualistic"], "4.5 22.2 4.5": ["charcters"], "2.5 2.4 8.3": ["notte"], "17.2 15.3 35.6": ["unmolded"], "11.1 10.8 -2.0": ["undulator"], "8.4 3.1 22.6": ["pudina"], "3.1 2.6 5.5": ["pretigious"], "11.0 18.4 10.1": ["woodenness"], "-8.0 2.5 3.5": ["rbds"], "7.3 -1.4 9.7": ["auxilary"], "-1.6 6.1 4.7": ["daugthers"], "5.3 20.1 16.1": ["shtupping"], "10.4 0.4 -1.0": ["nter"], "7.3 -0.1 -1.0": ["yeaterday"], "3.4 4.7 12.2": ["driveaway"], "1.0 14.4 12.9": ["onces"], "-2.2 2.9 3.1": ["mainlanes"], "14.4 1.2 35.6": ["brodo"], "9.9 3.7 7.0": ["shopkeeping"], "4.4 5.4 -0.0": ["electromyographic"], "5.9 13.8 0.9": ["vry"], "8.3 29.2 10.4": ["helots"], "3.8 25.4 5.5": ["kursi"], "1.2 4.7 16.1": ["winelist"], "8.2 11.0 11.3": ["tailwheel"], "10.2 19.4 2.2": ["sycophantically"], "6.3 10.7 19.5": ["cielo"], "5.4 3.7 8.8": ["datos"], "1.1 34.0 2.3": ["ghedli"], "4.6 -4.3 12.3": ["isoglucose"], "0.3 0.8 10.5": ["kwah"], "0.6 12.0 15.2": ["windpool"], "5.7 14.4 11.1": ["outcornered"], "-7.2 -6.7 5.3": ["freeship"], "13.0 6.2 10.0": ["nono"], "17.2 14.5 23.4": ["nightshades"], "5.4 9.0 4.5": ["uncluttering"], "10.2 10.8 7.9": ["chillaxing"], "3.0 10.5 4.0": ["essayistic"], "-1.5 16.8 6.9": ["plannings"], "6.7 9.9 4.0": ["nanocarrier"], "2.9 11.7 15.2": ["stuporous"], "2.8 9.6 -0.6": ["genuiness"], "4.4 9.6 5.9": ["disproval"], "0.2 11.8 20.7": ["carpe"], "15.7 10.8 38.7": ["catfishes"], "-3.3 5.0 7.8": ["polydrug"], "-1.3 5.0 10.6": ["buwan"], "10.0 5.6 21.2": ["heliconias"], "5.6 5.5 5.7": ["ofany"], "13.0 10.9 8.4": ["outdates"], "8.1 6.1 11.1": ["quizes"], "6.5 1.6 -0.6": ["citicoline"], "-10.5 10.8 13.1": ["revaccinations"], "9.4 13.6 17.5": ["fusiform"], "14.6 0.5 36.0": ["escalope"], "3.5 15.0 16.9": ["pictorialism"], "5.9 14.0 12.8": ["dansterpower"], "8.5 1.3 11.8": ["dumbwaiters"], "5.3 -0.9 12.6": ["salle"], "3.1 9.1 8.4": ["methylamine"], "2.6 29.5 6.5": ["interferer"], "-0.1 17.3 6.2": ["faceshield"], "12.9 3.5 10.7": ["rnb"], "12.9 7.5 12.2": ["diadems"], "1.3 24.2 5.0": ["servitor"], "6.1 6.7 4.4": ["radialisation"], "-8.4 1.5 3.6": ["sessionals"], "3.6 13.3 14.7": ["hhh"], "2.4 8.8 11.8": ["duda"], "8.9 3.5 9.8": ["hyeok"], "-5.4 4.6 7.7": ["primatial"], "5.7 28.2 5.0": ["maneuvres"], "8.3 -0.5 13.9": ["paraffins"], "-2.5 11.6 13.3": ["ablator"], "22.4 5.5 32.2": ["carv"], "12.9 10.6 11.4": ["prestidigitator"], "8.1 8.2 11.4": ["haulted"], "21.0 37.9 2.1": ["cyberwarriors"], "6.8 -3.7 4.8": ["ethinylestradiol"], "2.4 11.6 5.1": ["vedike"], "14.0 11.1 1.5": ["parnter"], "-0.5 7.0 0.3": ["resolvins"], "6.3 16.8 7.4": ["suttee"], "14.2 32.5 12.9": ["unbloodied"], "15.1 8.3 16.3": ["jouncing"], "-0.8 10.5 5.2": ["misutilisation"], "16.8 10.3 32.0": ["tomatoe"], "10.0 6.7 17.1": ["breadboards"], "4.8 2.9 2.4": ["rajasthan"], "18.8 20.7 10.9": ["spewers"], "13.6 -4.4 9.3": ["postoffice"], "-1.9 5.3 12.0": ["kayang"], "8.6 3.4 3.3": ["eka"], "-5.4 6.4 -4.2": ["councel"], "6.9 15.1 3.7": ["maradona"], "11.8 3.6 -7.0": ["monetises"], "18.7 12.0 10.3": ["asymetrical"], "18.2 5.9 28.2": ["tannish"], "13.0 -3.3 3.3": ["soling"], "10.4 12.1 20.4": ["inu"], "3.8 12.5 6.7": ["genitally"], "5.6 9.4 37.0": ["pawikan"], "12.4 7.7 10.0": ["rond"], "9.3 18.9 14.7": ["ballady"], "16.4 8.8 30.8": ["oreos"], "-6.6 -11.0 -4.9": ["interviewd"], "-2.6 16.9 -1.1": ["partitionist"], "-2.3 2.2 15.0": ["padron"], "5.2 6.1 14.8": ["akpeteshie"], "-1.9 18.7 7.6": ["brendan"], "10.3 21.5 22.9": ["daphnes"], "7.3 42.6 2.9": ["civilans"], "3.4 24.4 8.2": ["woodsball"], "1.2 13.0 5.7": ["affectivity"], "11.7 4.7 31.1": ["kamote"], "20.6 16.6 4.6": ["fetishising"], "1.4 6.1 13.0": ["granddaugher"], "-2.8 17.7 14.1": ["fren"], "3.5 10.7 4.6": ["migrane"], "4.4 19.4 16.4": ["roop"], "14.2 22.7 9.2": ["borking"], "18.0 12.9 14.6": ["storkling"], "0.1 4.9 15.8": ["umalis"], "10.4 2.3 8.2": ["procedes"], "1.7 19.2 4.1": ["servent"], "3.1 8.7 6.6": ["thrivers"], "1.7 14.0 0.0": ["thepresident"], "9.2 6.2 11.7": ["streamliners"], "18.1 -1.1 5.6": ["pannel"], "6.2 4.7 2.7": ["bhawan"], "4.5 -5.1 -6.2": ["unallowed"], "16.2 21.5 8.1": ["thumbpad"], "3.2 18.5 6.8": ["skyping"], "5.9 12.0 9.7": ["ludacris"], "9.2 -0.6 14.6": ["grwoth"], "2.8 9.9 1.3": ["evacuted"], "14.7 17.9 17.8": ["crosscurrent"], "13.3 16.8 16.9": ["hypnotises"], "11.6 22.8 7.2": ["lumpens"], "9.2 13.4 12.9": ["neet"], "35.6 14.3 27.4": ["beanstalks"], "0.5 -0.1 6.2": ["assayers"], "9.3 10.0 15.9": ["guinness"], "5.6 19.6 12.1": ["memsahib"], "9.3 19.8 12.0": ["usuall"], "0.7 15.6 10.0": ["unmutated"], "8.2 3.0 20.4": ["cherts"], "22.5 14.2 19.0": ["sunbird"], "7.5 8.6 9.5": ["crestal"], "8.5 11.3 12.2": ["solomon"], "17.2 15.8 30.9": ["toadflax"], "2.9 3.5 6.5": ["seriocomedy"], "-0.6 -6.5 6.0": ["vander"], "7.7 19.2 13.6": ["blitheness"], "-1.2 -8.5 -4.6": ["dutogliptin"], "-3.1 3.4 5.7": ["sists"], "28.3 -3.8 9.4": ["snowdome"], "-1.8 -3.9 2.5": ["serologist"], "-5.6 12.3 7.6": ["transfect"], "16.5 15.5 23.7": ["windburned"], "-1.8 27.9 7.8": ["inflictions"], "17.0 15.4 12.9": ["shrieker"], "-2.3 24.0 10.5": ["grumbler"], "-6.4 12.8 6.6": ["koinonia"], "-1.5 11.2 4.5": ["sporicidal"], "17.4 7.0 16.2": ["izzy"], "1.9 -2.5 5.9": ["edtion"], "1.6 -0.6 2.1": ["descibes"], "-1.6 11.1 7.1": ["marginable"], "4.1 13.7 1.9": ["defnitely"], "2.7 21.0 9.3": ["niave"], "-10.0 12.9 5.0": ["gialli"], "2.2 11.6 2.5": ["nonsafety"], "-0.6 12.7 4.3": ["downcycles"], "6.0 7.7 17.8": ["duri"], "3.5 20.5 8.4": ["theball"], "0.8 12.9 12.9": ["homefolks"], "5.3 -1.7 4.2": ["classs"], "-1.2 -3.0 4.4": ["averging"], "2.1 1.5 4.8": ["yahn"], "1.2 22.7 4.4": ["infantilizes"], "9.1 16.6 10.7": ["shastra"], "12.1 -0.2 20.0": ["flannelette"], "7.8 3.2 12.8": ["rogaine"], "34.1 19.2 16.1": ["exoskeletal"], "1.9 17.4 11.1": ["overdesign"], "16.3 15.2 12.9": ["craggier"], "13.2 10.4 12.4": ["latinas"], "13.7 19.4 13.1": ["excitably"], "-2.9 -5.5 -1.3": ["prgram"], "16.5 15.0 20.3": ["dogger"], "4.7 13.5 0.8": ["exagerrated"], "2.8 0.8 3.4": ["twn"], "12.0 7.2 18.3": ["toker"], "7.3 -0.4 15.3": ["fondo"], "-2.4 3.1 18.3": ["ulan"], "-0.5 9.3 13.0": ["khush"], "0.3 -0.9 13.6": ["proscar"], "8.9 8.5 27.5": ["sourdoughs"], "5.1 5.6 6.6": ["rdp"], "7.9 19.2 15.1": ["boet"], "-4.7 21.2 8.8": ["reckonable"], "5.6 0.0 11.6": ["nox"], "-5.0 14.2 5.1": ["excitotoxic"], "0.1 8.1 11.3": ["nonsalary"], "3.2 3.4 5.8": ["scor"], "7.8 13.1 17.2": ["sami"], "17.4 7.9 25.0": ["gracile"], "16.2 1.7 20.6": ["paluxysaurus"], "-2.0 3.6 -2.0": ["polemarker"], "0.7 4.7 14.7": ["antigenically"], "18.9 17.1 15.4": ["imperator"], "4.9 7.1 1.9": ["maruti"], "16.6 1.9 10.0": ["cupper"], "11.3 18.9 18.0": ["hoggish"], "4.6 7.6 10.6": ["mainshock"], "0.4 3.4 4.5": ["uder"], "-1.9 11.9 9.6": ["addressbook"], "7.6 12.0 8.0": ["passioned"], "13.5 10.1 14.9": ["scanties"], "9.5 6.3 11.4": ["hectopascals"], "9.6 -3.7 15.9": ["bifold"], "16.4 16.5 28.6": ["doodie"], "6.9 16.2 21.2": ["permabear"], "4.9 5.5 -3.5": ["goodware"], "8.7 -0.1 21.5": ["gilder"], "0.6 -4.3 8.0": ["jueves"], "0.5 6.8 13.8": ["pian"], "-2.4 -3.9 10.6": ["seisiun"], "13.6 11.6 13.6": ["miaowing"], "4.2 20.2 13.7": ["navaids"], "11.5 13.5 28.3": ["stiil"], "15.8 16.9 12.0": ["nusiance"], "13.6 16.1 12.8": ["goonish"], "18.5 7.2 24.2": ["sandfish"], "7.6 -4.4 3.7": ["parmi"], "7.0 9.8 9.9": ["unclasped"], "3.3 -4.0 6.3": ["kochi"], "3.2 8.0 16.1": ["jersy"], "-0.7 6.8 10.5": ["amu"], "12.9 11.0 37.4": ["widgeons"], "-10.4 32.9 -2.3": ["casulties"], "-3.0 -2.9 3.5": ["tazarotene"], "3.8 10.5 1.3": ["constitue"], "20.1 11.8 31.0": ["floatin"], "5.6 -6.6 6.9": ["ication"], "17.4 8.0 18.5": ["skateable"], "6.5 -1.5 13.9": ["thixotropic"], "1.4 -0.2 3.6": ["nonconstruction"], "12.8 10.6 33.1": ["corncrakes"], "8.8 5.7 22.1": ["montmorillonite"], "15.7 14.8 16.8": ["spheroidal"], "15.9 3.1 4.9": ["nonexecutives"], "1.2 14.3 7.9": ["groun"], "8.9 5.8 5.7": ["dwar"], "16.2 15.3 25.9": ["foxhunters"], "20.8 2.9 25.1": ["boatmaker"], "-2.8 8.0 21.4": ["southerns"], "11.3 37.1 6.3": ["countermine"], "5.4 12.6 18.3": ["microsporidia"], "2.2 10.2 3.1": ["downconverted"], "-3.1 11.9 -3.1": ["gurz"], "2.5 12.7 -5.0": ["romanticises"], "11.2 7.3 22.2": ["underglaze"], "4.1 11.4 1.7": ["defter"], "-0.7 5.0 18.0": ["maltier"], "11.5 4.5 0.3": ["tweeks"], "10.4 -15.8 10.0": ["isscheduled"], "4.8 6.8 -0.6": ["chk"], "15.7 -0.7 8.4": ["flury"], "12.9 7.4 10.6": ["funemployed"], "3.8 21.3 7.8": ["legalistically"], "3.8 12.1 8.7": ["maghrib"], "11.8 -0.8 4.6": ["nehn"], "15.9 16.8 16.3": ["slumberland"], "3.8 5.9 6.1": ["scalably"], "2.3 5.1 5.8": ["ende"], "-1.8 -5.5 18.3": ["nonseniors"], "20.1 22.2 15.5": ["asymetric"], "12.4 12.8 8.2": ["fellated"], "2.8 2.3 14.9": ["istanbul"], "12.0 9.3 8.2": ["phonecard"], "8.7 0.2 19.1": ["nicky"], "10.9 2.1 15.8": ["shiprepair"], "12.2 -5.3 2.0": ["aheadof"], "3.9 8.1 9.8": ["maxwell"], "10.4 13.3 12.8": ["denatures"], "8.0 19.4 8.7": ["delimiters"], "17.9 7.6 15.0": ["jpmorgan"], "2.4 -0.2 4.7": ["balesio"], "6.4 19.0 4.7": ["disabler"], "0.4 21.4 8.0": ["unharmful"], "13.4 5.9 11.8": ["dwn"], "16.3 10.7 14.7": ["stereopticon"], "-1.2 11.9 9.0": ["wahan"], "1.4 3.1 0.3": ["zeigt"], "7.2 0.1 4.8": ["sterilizable"], "-1.4 -9.9 15.8": ["fiveday"], "12.1 9.1 1.4": ["dominatrices"], "10.8 12.6 16.0": ["zhang"], "4.8 6.1 4.0": ["kyeyo"], "11.1 12.3 0.4": ["internationl"], "3.8 2.3 8.0": ["cpa"], "3.8 2.3 9.1": ["nomi"], "4.6 0.5 1.1": ["forfaiting"], "8.5 14.1 14.9": ["boulderhippy"], "0.2 4.1 12.5": ["pastorals"], "12.0 9.5 15.8": ["adatoms"], "-3.2 2.9 9.8": ["ovariectomy"], "8.2 16.8 11.3": ["supose"], "8.3 1.8 12.0": ["quickstart"], "-11.7 -1.8 11.4": ["payraise"], "-7.1 13.4 9.1": ["zaman"], "1.5 1.5 15.1": ["roselle"], "11.7 10.5 6.9": ["nanomechanics"], "8.3 15.2 6.8": ["uglied"], "2.0 -2.5 13.4": ["agronomical"], "2.5 7.7 21.4": ["loko"], "4.8 7.5 9.4": ["vasculopathy"], "17.2 15.9 13.4": ["coverflow"], "5.6 10.9 10.5": ["belfast"], "16.4 10.6 21.4": ["thinnish"], "5.6 30.7 11.8": ["paleocons"], "10.0 3.5 6.8": ["keysets"], "7.3 1.0 25.3": ["doz"], "-2.0 3.9 4.0": ["substituents"], "15.5 -1.9 13.2": ["sugarfree"], "5.8 12.4 13.2": ["recombinants"], "6.7 6.0 -4.0": ["resecure"], "15.3 15.7 38.6": ["leatherjackets"], "2.4 0.7 5.4": ["lapsit"], "2.6 4.4 6.3": ["remians"], "10.3 7.3 5.3": ["rader"], "-4.0 7.5 9.4": ["methylate"], "4.1 9.9 -2.4": ["editorialise"], "13.2 7.0 -0.5": ["obsoletes"], "15.2 25.9 17.9": ["tribemate"], "9.5 11.6 18.5": ["nucleic"], "16.8 0.3 19.1": ["hayday"], "5.1 -1.8 12.0": ["muller"], "11.5 19.1 15.4": ["shyte"], "0.0 1.7 4.4": ["ryul"], "14.6 20.3 12.3": ["nooooooo"], "5.9 2.4 17.0": ["multicomputer"], "-4.0 4.0 3.9": ["mitigant"], "18.6 15.4 12.2": ["rustlings"], "20.1 8.5 -0.8": ["anticonsumer"], "-0.5 7.8 3.5": ["movi"], "8.0 4.7 4.4": ["deutschen"], "17.2 2.3 14.2": ["blockish"], "-0.7 0.4 1.9": ["labetalol"], "1.2 -1.2 1.8": ["denovo"], "6.7 22.8 7.6": ["wounder"], "8.0 8.3 17.2": ["stylizations"], "3.2 9.8 11.1": ["paromomycin"], "-2.7 7.8 5.3": ["supernatants"], "4.8 17.3 7.3": ["profounder"], "21.3 -4.1 7.3": ["windpark"], "20.4 11.7 23.2": ["hatpin"], "18.2 8.9 0.9": ["videodisc"], "-0.6 25.7 5.4": ["tahadiyeh"], "17.9 16.8 16.9": ["rumormonger"], "6.0 9.4 17.9": ["digestifs"], "12.8 3.7 13.1": ["aeroponic"], "18.3 2.6 5.4": ["webshops"], "7.9 12.0 16.9": ["hoity"], "10.5 -5.3 6.1": ["bookrunning"], "8.0 1.4 7.1": ["jaipur"], "11.6 6.0 5.5": ["battlebus"], "5.7 8.7 6.1": ["zlib"], "16.0 5.9 16.7": ["cannonballing"], "7.4 17.3 5.0": ["medicalising"], "0.3 12.0 6.5": ["testo"], "9.7 0.8 26.2": ["plasticulture"], "9.6 20.7 10.0": ["cockloft"], "5.5 6.8 6.9": ["premire"], "16.1 13.5 11.2": ["railtrack"], "3.1 -10.1 2.4": ["reseacher"], "11.1 13.0 14.7": ["cacophonies"], "9.3 -4.0 -1.6": ["smallprint"], "0.2 25.2 6.1": ["imperitive"], "9.5 4.3 11.0": ["palmas"], "10.2 10.8 -0.9": ["georeferencing"], "10.7 -2.8 9.3": ["reisling"], "0.6 6.8 14.8": ["aata"], "11.1 11.6 2.5": ["allegeldy"], "15.6 0.1 28.2": ["yau"], "12.9 2.0 -2.6": ["annotators"], "5.8 11.5 5.0": ["sitll"], "1.6 9.3 4.8": ["opacification"], "8.6 38.1 6.4": ["obscurant"], "8.3 13.4 10.4": ["ukraine"], "14.5 13.6 7.7": ["sledgehammered"], "3.6 8.0 13.2": ["inhomogeneity"], "16.9 9.4 26.1": ["tendu"], "16.0 8.4 14.4": ["underregulated"], "5.3 9.5 16.8": ["dhe"], "10.0 16.6 28.6": ["markhor"], "2.8 24.5 2.7": ["hotheadedness"], "10.1 4.1 19.6": ["minimus"], "-1.3 0.6 5.3": ["microsomal"], "1.4 1.9 -7.4": ["presidentof"], "6.5 23.9 6.2": ["obfuscator"], "4.2 18.0 11.2": ["hapen"], "5.5 10.5 17.9": ["ingression"], "5.3 6.7 17.4": ["urupa"], "1.6 1.8 -4.5": ["identfied"], "1.7 17.3 4.6": ["upbuilding"], "1.8 8.5 1.6": ["anonymisation"], "-8.9 -4.1 0.6": ["kbits"], "6.5 -4.4 2.2": ["nonaudit"], "5.9 9.4 10.0": ["nyaya"], "8.8 12.5 28.9": ["plumerias"], "8.4 17.4 3.8": ["offisde"], "3.1 -5.3 7.2": ["mbo"], "-1.2 6.0 13.9": ["tatlo"], "2.4 4.5 9.0": ["registred"], "6.1 11.0 0.8": ["russellm"], "-1.5 -1.9 2.2": ["carboxy"], "-5.0 6.0 1.2": ["bronchoscopies"], "-9.9 20.7 8.3": ["construal"], "10.9 1.2 9.3": ["nonvoice"], "3.0 4.8 7.0": ["myalgias"], "2.3 6.3 6.5": ["parameterisation"], "7.4 -0.7 4.8": ["secod"], "2.4 4.8 11.3": ["meaures"], "3.9 7.1 2.1": ["fived"], "5.5 13.1 8.3": ["monoglot"], "25.9 20.8 23.3": ["seadog"], "2.4 9.7 8.6": ["longview"], "1.7 6.6 21.5": ["koshering"], "20.6 12.3 5.7": ["collaspe"], "15.1 0.2 13.9": ["mejores"], "-1.8 10.8 11.9": ["aartis"], "3.8 10.1 -5.8": ["wellestablished"], "7.9 10.3 7.6": ["verykool"], "-5.0 -2.5 0.7": ["coinvestigator"], "8.5 9.6 34.7": ["nonmigratory"], "5.6 12.2 12.4": ["ecumenicism"], "-1.6 5.1 6.3": ["tomarket"], "5.5 9.0 13.7": ["bho"], "7.6 17.6 10.9": ["nuclides"], "20.9 9.8 21.4": ["jiff"], "13.1 10.3 9.9": ["enwrapped"], "5.9 5.9 34.1": ["udang"], "4.9 12.8 1.2": ["trinational"], "4.8 6.6 -1.3": ["aggregrate"], "-1.1 15.8 7.5": ["transcendentalists"], "16.7 -2.9 9.1": ["footwears"], "15.9 9.7 10.9": ["shoutfests"], "4.9 7.7 2.1": ["dois"], "4.9 9.9 6.2": ["heliophysics"], "2.8 8.9 6.1": ["renominates"], "7.3 1.8 20.4": ["fbm"], "15.1 19.3 11.8": ["potentialy"], "0.7 6.9 1.8": ["reshown"], "9.1 4.7 11.3": ["shlubs"], "-2.9 8.4 2.5": ["ongbi"], "22.1 30.1 28.4": ["destructo"], "1.3 19.4 10.6": ["symlink"], "6.9 18.4 11.8": ["umble"], "10.8 11.5 4.8": ["affilation"], "8.1 6.2 16.4": ["lashline"], "-0.0 9.5 5.6": ["eran"], "8.7 23.1 8.1": ["basely"], "9.9 -3.2 12.2": ["toolroom"], "8.7 17.3 10.2": ["sedulous"], "6.8 15.7 18.8": ["geohazard"], "24.4 8.1 -0.2": ["littleknown"], "16.2 35.9 20.1": ["annihilator"], "8.4 4.8 9.8": ["unelectrified"], "2.0 4.2 -1.2": ["writter"], "10.9 10.9 6.4": ["noisey"], "9.2 2.5 29.1": ["gou"], "12.3 6.4 15.0": ["wickers"], "18.4 2.9 33.5": ["gyotaku"], "24.5 3.8 12.7": ["cyberspying"], "16.5 13.3 15.7": ["andsome"], "8.2 13.2 13.6": ["ummmmm"], "1.9 3.0 12.3": ["lancaster"], "0.5 7.3 9.4": ["psoas"], "13.8 20.9 20.1": ["cardsharp"], "12.9 2.5 22.9": ["postholiday"], "11.5 3.8 18.2": ["tributyltin"], "-5.1 3.2 1.0": ["matin"], "2.0 9.0 15.6": ["godbrother"], "-0.1 6.9 -1.8": ["hapy", "foucs"], "6.4 11.6 11.0": ["ashok"], "11.0 9.8 27.3": ["foliaged"], "3.4 11.6 7.4": ["kown"], "4.2 14.0 31.7": ["tyers"], "9.7 7.6 6.3": ["aftter"], "-5.2 3.6 9.9": ["dysmenorrhoea"], "7.1 11.0 19.6": ["rainboots"], "18.1 3.0 3.2": ["similary"], "12.6 27.7 14.2": ["shotblockers"], "5.0 26.5 13.8": ["extremeness"], "14.8 15.8 8.5": ["nonprofitable"], "-1.0 5.5 17.4": ["didto"], "9.1 15.9 10.2": ["armenian"], "16.7 22.8 6.5": ["unfaith"], "7.6 -3.4 4.6": ["nihn"], "12.8 5.4 6.8": ["helf"], "10.0 26.9 15.6": ["shootable"], "8.0 1.5 19.4": ["shang"], "9.0 9.4 10.0": ["bodyshells"], "8.1 11.7 21.1": ["terrior"], "19.6 21.2 19.2": ["unsheathes"], "-2.6 19.7 4.7": ["dhimma"], "6.5 15.8 15.2": ["airstreams"], "11.5 16.9 9.5": ["antiparallel"], "11.5 14.8 13.9": ["boyars"], "-0.3 -1.3 19.0": ["solera"], "0.6 16.7 10.4": ["dysentry"], "4.3 4.8 7.5": ["colourisation"], "19.4 16.9 25.0": ["cheeps"], "9.8 8.4 39.0": ["spoonbread"], "-1.4 14.9 8.7": ["fisking"], "16.4 9.4 16.2": ["zulu"], "12.2 1.1 18.5": ["cruisewear"], "-11.7 3.4 4.6": ["alia"], "1.9 0.9 5.1": ["poller"], "5.9 8.0 5.4": ["movimiento"], "13.2 7.5 5.1": ["liquification"], "-1.4 6.5 7.7": ["umphakatsi"], "15.1 7.8 3.7": ["nanocircuits"], "13.8 11.1 6.1": ["firesales"], "5.2 18.5 8.1": ["equites"], "21.1 30.5 22.4": ["limeys"], "27.1 19.3 23.6": ["golfballs"], "17.2 18.0 2.5": ["ritish"], "12.6 14.0 7.4": ["gravitons"], "2.5 9.0 14.0": ["pitchiness"], "-1.2 11.6 4.1": ["randomise"], "12.8 15.8 4.3": ["usefullness"], "10.1 9.5 17.4": ["jibbers"], "4.3 9.1 -13.8": ["involvedin"], "1.7 12.9 15.5": ["appositive"], "5.1 8.3 16.2": ["greenscape"], "17.4 13.7 -2.3": ["bulit"], "3.2 4.3 5.3": ["effet"], "15.9 6.0 7.1": ["dowturn"], "8.4 12.4 14.7": ["zey"], "-2.7 19.0 17.3": ["gimmees"], "9.1 16.9 15.0": ["theground"], "1.6 16.1 5.4": ["conventionalism"], "10.7 11.9 26.6": ["nipah"], "5.6 6.7 13.0": ["doy"], "-1.8 22.0 3.5": ["azad"], "-4.3 19.2 11.2": ["painfulness"], "2.5 10.4 7.3": ["zikr"], "17.2 2.8 17.1": ["tooter"], "6.2 2.2 11.1": ["duringa"], "17.6 12.0 9.7": ["overstyled"], "9.4 -2.2 6.4": ["rangeof"], "2.6 -1.2 12.2": ["showlist"], "-5.9 13.3 -5.0": ["principlist"], "10.6 11.3 5.1": ["dividable"], "8.4 4.0 0.8": ["propsects"], "2.5 -5.1 8.5": ["eisteddfodau"], "6.8 9.6 16.0": ["klunky"], "6.4 -1.4 17.4": ["salopettes"], "13.7 16.1 7.7": ["suckiest"], "1.5 3.0 6.5": ["dato"], "-0.3 9.6 7.2": ["toxigenic"], "10.3 13.0 9.5": ["lacerates"], "11.6 12.1 38.8": ["willets"], "17.6 25.1 7.9": ["papparazi"], "5.5 20.5 16.3": ["acnes"], "13.9 3.3 38.9": ["mozarella"], "1.2 6.4 4.6": ["shloka"], "0.0 -0.2 14.1": ["accessorial"], "3.8 -0.7 1.5": ["lihn"], "-1.8 6.4 -1.2": ["radioprotective"], "0.7 -0.2 14.8": ["topis"], "3.3 1.5 1.5": ["folllowed"], "7.4 10.6 5.6": ["fiv"], "7.4 15.9 2.8": ["manyof"], "9.3 6.5 11.2": ["chessers"], "-0.8 17.1 0.9": ["oncoproteins"], "3.2 23.9 2.5": ["defilements"], "0.2 3.7 11.4": ["ethnographical"], "17.4 16.7 26.9": ["acidifies"], "17.4 13.0 13.6": ["drayman"], "1.3 16.6 14.5": ["tranquilo"], "6.5 3.2 30.5": ["dinuguan"], "10.4 -4.1 35.4": ["vongole"], "22.0 16.2 24.5": ["popple"], "5.5 3.4 9.7": ["venice"], "7.6 3.0 2.5": ["posteromedial"], "6.1 -7.6 11.6": ["bfinance"], "11.8 10.0 31.5": ["brevetoxin"], "-4.3 12.1 0.1": ["herpetic"], "15.5 20.2 12.9": ["boneyards"], "1.5 8.8 1.5": ["imate"], "30.1 4.4 14.3": ["profts"], "3.7 9.4 13.7": ["ribbings", "buona"], "11.1 13.7 15.1": ["pentaquark"], "3.9 6.1 0.9": ["timestamping"], "-0.6 9.3 5.6": ["motoneurons"], "9.0 5.4 10.4": ["popwreck"], "9.6 6.0 5.2": ["reamined"], "-7.1 14.6 2.0": ["specifiy"], "16.0 0.5 13.7": ["souveniers"], "17.8 13.6 11.4": ["neaby"], "20.0 4.0 20.4": ["verts"], "14.6 13.2 20.8": ["semiconsciousness"], "-2.1 7.7 -0.7": ["defrags"], "-4.9 -0.8 5.7": ["nata"], "2.0 16.3 4.5": ["askers"], "4.3 6.9 12.7": ["sulfer"], "15.0 17.6 3.8": ["pasing"], "-5.6 3.6 -2.8": ["silentlambs"], "5.0 -9.4 6.0": ["showflat"], "24.6 20.5 16.4": ["succubi"], "8.8 16.6 12.3": ["gruppetto"], "6.0 3.4 4.6": ["lookbooks"], "13.7 7.9 4.8": ["relink"], "7.9 11.3 22.8": ["rodney"], "12.5 8.9 12.7": ["producton"], "0.7 12.9 7.1": ["consternated"], "10.1 3.5 19.4": ["tiedown"], "9.2 26.7 4.1": ["undiscoverable"], "6.0 -3.0 9.4": ["rding"], "10.7 6.1 16.4": ["puerto"], "2.3 -2.7 1.4": ["transtec"], "0.6 6.2 11.4": ["respeto"], "14.7 6.3 15.8": ["cablecar"], "-3.5 -10.6 2.4": ["backfile"], "7.3 1.2 16.4": ["onehalf"], "14.0 4.9 14.1": ["foodstalls"], "16.2 -1.0 11.1": ["agritech"], "-0.3 6.0 7.9": ["occaisions"], "13.1 -2.8 1.4": ["secur"], "3.7 7.3 11.0": ["fermentative"], "14.6 15.4 24.6": ["gaper"], "2.2 0.2 9.8": ["slinkier"], "5.5 8.1 6.2": ["evironment"], "-2.6 14.8 8.6": ["ocurring"], "2.4 6.7 9.0": ["interesection"], "2.1 4.3 -0.9": ["keeness"], "17.2 6.9 7.6": ["solutionsfor"], "11.6 6.9 6.1": ["antoher"], "5.6 6.2 9.1": ["articulators"], "10.4 20.9 7.7": ["butthurt"], "8.3 13.8 14.8": ["glisters"], "0.9 2.6 29.2": ["verdes"], "6.6 6.6 20.0": ["swayback"], "2.2 0.8 29.4": ["potlatches"], "8.7 0.2 15.9": ["charreada"], "14.5 25.5 12.5": ["subconcious"], "17.4 2.7 8.7": ["earnigns"], "4.2 11.7 4.7": ["baroquely"], "10.4 35.6 10.9": ["warhawk"], "8.5 5.8 7.5": ["alcholic"], "-7.8 7.5 -3.1": ["accommodator"], "11.3 22.5 -1.5": ["propagandise"], "-4.8 6.0 0.1": ["thant"], "6.5 0.3 9.0": ["mucha"], "-8.9 1.7 7.6": ["parapro"], "-1.6 1.6 9.3": ["autonomically"], "-1.3 6.0 4.4": ["andn"], "6.2 13.4 16.0": ["creoles"], "3.2 18.5 11.0": ["overcritical"], "5.2 15.7 14.0": ["thng"], "-4.0 6.6 -1.1": ["parishat"], "-2.8 -7.5 1.9": ["embolics"], "5.5 14.1 11.3": ["victms"], "7.7 -2.5 10.6": ["indu"], "8.7 26.5 5.8": ["proselytes"], "19.1 10.5 9.4": ["fluffers"], "6.9 5.1 7.0": ["zimmer"], "-4.2 17.3 13.0": ["unenumerated"], "0.5 -1.9 7.9": ["widerange"], "-0.2 5.7 12.7": ["additively"], "11.9 9.7 8.7": ["stumblers"], "-4.5 14.8 9.7": ["ownself"], "4.1 8.4 13.6": ["jalan"], "9.9 -0.7 10.0": ["chello"], "2.8 7.5 1.1": ["amortizable"], "12.0 13.3 9.8": ["chicklets"], "13.4 7.7 24.9": ["stegosaurs"], "4.2 6.9 0.7": ["launderings"], "4.3 18.2 -1.2": ["flagitious"], "18.0 8.1 7.3": ["acoss"], "5.7 9.3 -1.3": ["inister"], "15.0 4.9 6.9": ["mechnical"], "-0.8 0.1 6.5": ["surgury"], "18.6 20.0 7.7": ["fuckwit"], "6.3 9.9 -5.3": ["ebike"], "12.9 6.9 1.4": ["eanwhile"], "14.1 13.2 19.3": ["naturalizes"], "4.9 15.7 9.7": ["unworkability"], "4.9 7.6 8.4": ["convient"], "5.6 14.7 13.5": ["chargin"], "12.7 7.2 34.8": ["nopalitos"], "-1.8 11.8 5.9": ["hypoventilation"], "12.5 3.0 21.2": ["zhou"], "23.0 9.0 28.7": ["umbels"], "4.9 15.9 2.3": ["witnesss"], "1.6 9.2 14.4": ["yesses"], "4.1 3.2 2.0": ["weiterhin"], "10.5 16.8 7.1": ["blabbered"], "14.1 15.5 47.9": ["ragworm"], "3.2 11.8 6.5": ["annunciators"], "0.4 7.4 13.6": ["yeilding"], "9.0 12.1 22.3": ["jonquil"], "7.7 4.1 14.1": ["overa"], "3.6 -9.4 11.4": ["baldwin"], "5.8 4.1 9.7": ["schoolbuildings"], "8.9 0.2 5.1": ["madea"], "13.7 5.2 15.7": ["trews"], "11.5 2.5 6.4": ["childcarers"], "8.2 4.1 5.5": ["insufflation", "sibility"], "10.7 -3.1 -3.8": ["firmenpresse"], "17.5 17.9 16.8": ["chirpers"], "0.2 -2.8 4.4": ["mesalazine"], "5.4 19.5 2.0": ["curruption"], "-3.8 -7.8 10.1": ["ctns"], "-1.3 14.9 -0.2": ["appologise"], "19.9 1.9 6.2": ["subpeonas"], "8.8 14.3 2.4": ["vtap"], "5.8 14.5 28.1": ["rhizomatous"], "5.1 3.3 12.3": ["polyglutamate"], "8.6 3.1 16.8": ["ripstop"], "10.3 14.2 4.4": ["gemacht"], "-6.1 10.6 8.4": ["resocialization"], "6.1 8.8 12.9": ["gareth"], "14.5 18.4 16.6": ["smogs"], "-1.9 5.9 6.7": ["luliconazole"], "-2.2 22.4 9.8": ["abbas"], "15.9 -1.9 -4.9": ["krijgt"], "4.1 9.8 5.9": ["sensationalisation"], "3.8 1.7 9.0": ["zinesters"], "7.8 5.3 22.5": ["sportsboats"], "6.9 5.2 5.8": ["neded"], "4.3 -5.0 15.5": ["eup"], "13.2 14.3 21.7": ["honkey"], "2.9 11.3 5.3": ["moive"], "2.9 11.1 33.4": ["shoaled"], "10.3 5.6 9.7": ["muito"], "10.4 8.8 12.1": ["kecks"], "17.9 6.7 4.6": ["onine"], "10.4 16.0 9.4": ["obsolesce"], "18.6 24.6 5.7": ["inpenetrable"], "18.0 9.0 20.0": ["shiplift"], "13.1 -0.8 9.0": ["fifteenfold"], "10.4 12.3 16.5": ["haaa"], "11.2 18.1 19.8": ["palatably"], "9.0 8.2 10.8": ["motorycle"], "6.9 15.1 11.4": ["thinky"], "3.6 2.7 17.7": ["cellularity"], "2.7 11.5 8.6": ["nico"], "4.6 18.2 15.3": ["rototilled"], "7.7 14.3 14.3": ["sarovar"], "1.6 0.5 4.1": ["recommeded"], "4.4 7.2 19.3": ["miz"], "12.8 13.8 15.2": ["outproducing"], "16.2 2.8 38.5": ["whalemeat"], "6.0 15.5 6.9": ["unstarry"], "12.1 1.9 8.2": ["revivial"], "1.8 16.2 1.0": ["hypothetic"], "-0.4 14.8 4.1": ["tzedek"], "2.2 11.4 22.1": ["papilla"], "5.5 6.7 5.0": ["evi"], "-6.3 -2.4 -1.1": ["quitclaimed"], "1.9 12.8 9.5": ["reportee"], "10.0 -0.0 -3.6": ["vielife"], "14.1 19.6 7.3": ["mythmaker"], "15.8 9.6 4.6": ["tubthumping"], "4.0 1.6 18.9": ["jennings"], "5.1 4.6 14.8": ["gamekeeping"], "25.2 9.0 17.8": ["bedframe"], "0.4 8.3 7.9": ["datuk"], "14.5 11.6 19.3": ["wharfie"], "8.7 17.3 6.3": ["landrover"], "7.4 25.8 9.4": ["mettlesome"], "9.5 22.9 9.0": ["desafuero"], "5.7 19.9 16.7": ["corporeality"], "-2.3 28.2 1.4": ["enemity"], "11.8 15.9 21.1": ["potentilla"], "8.3 10.3 16.1": ["pustular"], "-7.1 -6.5 8.8": ["subgrant"], "7.4 19.9 19.3": ["recrossing"], "10.6 5.8 1.6": ["watchphone"], "13.3 21.5 17.3": ["spaded"], "-1.0 5.7 4.8": ["speedtest"], "4.9 4.8 17.1": ["ironworking"], "12.7 1.3 14.2": ["treck"], "9.6 19.7 7.8": ["amock"], "3.9 -7.4 18.7": ["ropings"], "7.8 10.5 16.9": ["leatherman"], "9.2 6.6 6.7": ["abortuary"], "3.2 10.2 8.2": ["alkyne"], "2.4 13.0 4.2": ["denn"], "18.5 11.2 12.4": ["fannying"], "12.8 12.7 26.1": ["unthawed"], "7.1 7.6 8.3": ["microfinanciers"], "9.1 7.4 10.1": ["historique"], "15.0 10.7 24.3": ["sailmaking"], "25.7 23.2 15.8": ["slingshotting"], "12.0 2.6 27.6": ["kahlua"], "13.3 12.6 0.0": ["metrication"], "9.9 27.3 7.7": ["mortifies"], "-3.4 14.6 12.4": ["soch"], "4.3 7.2 5.1": ["untackled"], "4.8 6.3 3.7": ["homotaurine"], "8.3 11.6 16.0": ["thermophilum"], "7.2 25.0 5.9": ["asymptotically"], "8.9 2.5 6.5": ["ethoxylates"], "2.0 13.6 7.6": ["sextortion"], "8.8 4.4 3.2": ["pourraient"], "4.6 19.3 11.2": ["harlotry"], "7.5 10.3 25.9": ["tahu"], "10.3 -0.9 18.3": ["alehouses"], "10.0 0.9 32.7": ["pansit"], "-3.1 7.4 9.6": ["marunong"], "20.0 16.4 11.1": ["tocsin"], "7.8 2.6 25.7": ["eggnogs"], "7.8 0.2 2.3": ["tria"], "7.0 15.8 -6.1": ["arived"], "11.3 9.0 9.4": ["convincer"], "12.4 16.8 19.7": ["charley"], "1.9 -7.8 3.0": ["rale"], "12.6 2.2 5.2": ["embroided"], "3.3 14.1 14.3": ["scen"], "27.4 6.8 19.6": ["incased"], "6.6 2.1 0.2": ["subcommitee"], "17.4 1.8 41.3": ["girolles"], "-1.1 2.4 0.0": ["clubmaking"], "11.6 -1.7 2.4": ["visualisers"], "8.6 14.2 21.8": ["replikins"], "-1.9 10.6 7.5": ["plausable"], "-2.5 1.6 11.4": ["atten"], "0.9 20.5 13.5": ["dailiness"], "-3.1 30.2 2.9": ["democide"], "1.8 14.9 -4.0": ["inportant"], "14.2 4.0 21.1": ["bumber"], "12.3 5.6 9.4": ["chondrite"], "-2.2 14.1 9.6": ["mwana"], "7.7 2.2 10.9": ["monoshock"], "7.0 13.4 1.6": ["conjur"], "-1.0 12.5 15.8": ["nakaka"], "2.6 4.5 4.0": ["farmouts"], "-3.5 5.6 16.1": ["konting"], "22.7 31.4 14.3": ["batarang"], "-0.6 -3.7 7.4": ["charitybuzz"], "2.6 8.9 11.7": ["taans"], "10.7 0.7 6.9": ["pagina"], "10.1 -1.0 13.3": ["conta"], "13.4 -2.9 7.1": ["clotheshorses"], "14.6 8.3 7.1": ["unairconditioned"], "7.4 10.6 5.7": ["evro"], "7.9 0.0 11.3": ["mawr"], "16.0 5.4 22.2": ["maritimes"], "1.2 -1.7 7.3": ["scholarshipped"], "1.0 2.1 13.7": ["mucins"], "5.4 10.6 0.9": ["tionary"], "13.1 -2.7 4.1": ["thirtyfold"], "5.2 3.2 11.4": ["venu"], "13.0 16.1 11.4": ["underbodies"], "16.4 23.8 13.3": ["frankenstein"], "17.1 7.1 -3.0": ["whizkids"], "4.2 -5.6 6.2": ["hof"], "0.8 6.7 4.6": ["twogame"], "16.7 9.1 11.2": ["zoomy"], "19.6 15.8 22.7": ["cryptid"], "13.7 9.2 5.2": ["submillimetre"], "-5.2 -11.3 -0.7": ["reschedulings"], "-2.0 -9.6 -0.2": ["sheh"], "6.4 2.1 7.8": ["ekta"], "22.3 3.0 22.5": ["chalkware"], "-2.1 8.9 -1.2": ["memb"], "3.1 15.1 4.1": ["drillmaster"], "3.2 5.6 16.6": ["kristin"], "6.0 -3.9 10.4": ["wahn"], "16.7 21.3 24.5": ["sirocco"], "3.8 0.7 2.1": ["func"], "5.4 0.7 2.5": ["aftenoon"], "2.9 11.7 9.2": ["adifferent"], "-0.5 1.0 -2.4": ["practic"], "0.1 12.7 10.4": ["sylvinite"], "-0.7 5.3 11.5": ["opiods"], "5.8 2.0 10.2": ["llamado"], "-1.1 8.1 21.8": ["sping"], "-11.4 7.5 14.0": ["neti"], "14.5 0.5 5.5": ["grote"], "10.3 -1.8 0.7": ["wint"], "10.8 -5.4 10.8": ["facililty"], "9.4 3.8 14.4": ["corroboree"], "11.7 17.2 24.1": ["arrr"], "6.5 6.5 12.0": ["leah"], "-5.6 -2.8 17.7": ["overallocated"], "2.3 5.8 -0.3": ["ipadio"], "20.5 9.2 5.9": ["varient"], "12.5 6.6 13.0": ["bushlands"], "5.0 11.6 20.2": ["belty"], "-1.6 0.7 7.3": ["tositumomab"], "-5.2 12.1 -0.4": ["dividedness"], "1.7 21.9 8.4": ["byrd"], "8.3 13.4 11.1": ["ultrazoom"], "1.5 17.9 3.7": ["outmanaged"], "11.9 10.3 4.7": ["twttr"], "-0.9 18.8 9.2": ["tahdiya"], "6.2 3.9 4.6": ["airflights"], "11.6 1.1 -2.2": ["terrabytes"], "18.9 13.3 21.5": ["paloverde"], "-6.3 3.1 4.4": ["trackdays"], "6.7 -1.0 8.8": ["offici"], "-9.4 -3.6 2.4": ["hysteroscopic"], "1.4 12.3 22.3": ["viewscapes"], "-0.8 5.0 0.4": ["autor"], "16.3 0.5 28.6": ["formaggio"], "6.1 -0.2 8.1": ["uganda"], "5.6 -0.9 18.2": ["breat"], "5.0 18.4 4.7": ["aclu"], "22.1 7.7 3.6": ["hypercharged"], "9.7 8.5 15.7": ["primordia"], "14.6 4.8 4.5": ["casette"], "7.2 21.8 13.3": ["banally"], "3.8 9.1 12.5": ["granddogs"], "12.1 26.7 11.3": ["nexuses"], "10.4 -2.5 7.0": ["jaune"], "7.8 4.8 15.4": ["acini"], "4.1 10.3 7.3": ["monodisperse"], "8.0 1.4 1.4": ["diginet"], "4.0 5.4 3.9": ["coord"], "8.6 7.1 11.5": ["shorefronts"], "2.6 20.4 18.6": ["bishounen"], "-1.6 -4.2 2.5": ["tations"], "11.6 3.0 22.3": ["schnoodle"], "0.3 8.9 -6.5": ["orgnisations"], "20.0 9.8 30.8": ["flowerless"], "2.6 6.2 -2.5": ["adipiplon"], "2.3 20.0 3.7": ["overinvolved"], "13.1 2.9 36.8": ["avgolemono"], "16.7 20.4 17.9": ["milady"], "-4.3 0.8 13.3": ["anovulation"], "6.8 14.7 4.4": ["ideo"], "0.8 12.1 9.7": ["talke"], "20.4 1.9 8.6": ["movieplex"], "1.4 14.1 19.5": ["acephate"], "-4.7 7.2 -7.0": ["doubtfull"], "5.5 7.9 10.5": ["hexamer"], "10.6 6.2 20.0": ["sulfidic"], "9.2 11.2 12.6": ["gameball"], "-2.6 7.0 -0.0": ["invididual"], "4.4 7.9 15.6": ["blondeness"], "8.0 8.1 9.1": ["manangement"], "-8.3 -9.4 3.8": ["ald"], "13.6 8.9 12.1": ["nebulosity"], "21.1 11.2 27.1": ["cinquefoil"], "-12.3 6.0 1.2": ["yeshivos"], "5.2 10.5 0.6": ["nulled"], "11.0 11.1 26.6": ["canoing"], "14.2 7.3 16.4": ["swagga"], "5.9 -4.3 7.7": ["cumulates"], "2.2 4.6 6.7": ["subsituted"], "7.9 2.2 11.3": ["flanging"], "5.4 3.3 2.9": ["triplication"], "4.3 2.0 1.3": ["rearchitect"], "6.2 1.5 0.0": ["powercash"], "-0.2 0.4 5.1": ["reactogenicity"], "7.9 -10.3 -5.9": ["dicusses"], "1.5 20.3 13.7": ["whot"], "7.1 8.4 9.4": ["woodpushers"], "3.7 7.2 13.0": ["allegretto"], "8.3 4.9 5.0": ["viles"], "4.2 15.7 12.5": ["palacios"], "12.9 8.7 24.1": ["polydactyl"], "13.5 -6.4 -5.0": ["aninternational"], "5.9 6.1 14.4": ["myasthenia"], "17.9 5.4 11.1": ["prezzie"], "2.3 -1.0 3.1": ["twobedroom"], "12.8 11.0 13.5": ["cherty"], "6.7 13.5 -1.1": ["readapting"], "12.1 20.3 7.5": ["grisliness"], "-11.1 -8.8 -4.8": ["ership"], "17.2 11.7 10.8": ["shepherdesses"], "1.7 19.6 12.3": ["cessations"], "2.7 19.6 9.6": ["rapprochements"], "3.2 8.5 1.6": ["skysports"], "6.4 45.7 8.2": ["bombsight"], "-2.4 4.0 6.4": ["nning"], "16.7 0.9 15.2": ["neighs"], "13.3 22.0 8.0": ["immiserated"], "7.8 11.3 9.0": ["neutralizers"], "13.0 13.9 7.5": ["photoshops"], "16.6 13.6 3.6": ["pootle"], "5.0 27.3 -0.1": ["propagandising"], "20.8 13.1 13.7": ["permabears"], "3.3 28.2 2.3": ["duplicities"], "6.8 19.9 9.1": ["declinism"], "7.6 15.0 15.7": ["morphogens"], "3.2 11.4 38.1": ["kinilaw"], "15.3 3.5 12.9": ["nvestors"], "8.9 18.2 15.9": ["upgra"], "9.4 7.5 10.7": ["tims"], "9.1 11.7 22.9": ["brusher"], "20.0 8.4 9.0": ["collpased"], "11.1 8.9 18.9": ["conserva"], "5.3 10.8 6.2": ["cuse"], "1.0 8.6 -4.5": ["offiical"], "4.7 1.5 14.7": ["gwneud"], "6.3 4.5 9.6": ["bioflavonoid"], "4.2 5.4 12.3": ["hyon"], "3.9 17.4 0.4": ["succomb"], "10.7 1.9 12.4": ["rfc"], "-0.2 12.3 5.6": ["looseheads"], "4.6 12.8 2.6": ["succombed"], "9.6 6.1 7.5": ["fams"], "10.6 4.7 0.2": ["developmentand"], "21.2 9.0 17.8": ["begrimed"], "-1.3 3.7 9.2": ["resu"], "-5.1 9.2 12.9": ["accidentals"], "-14.3 6.1 0.7": ["reliabilities"], "17.3 9.8 18.8": ["koppie"], "2.4 13.7 7.7": ["winge"], "3.0 14.0 17.1": ["benchrest"], "-1.9 8.7 6.0": ["spped"], "10.9 5.0 0.0": ["easycash"], "2.4 13.4 8.2": ["ascerbic"], "8.8 18.6 18.0": ["outland"], "-5.0 7.7 14.4": ["complexing"], "14.2 0.7 20.7": ["hilo"], "10.2 7.8 13.3": ["comodity"], "6.0 22.6 10.3": ["comeuppances"], "18.3 21.4 13.4": ["unbeautiful"], "8.2 -3.7 17.6": ["growthy"], "4.2 23.6 7.6": ["indirectness"], "8.4 20.2 12.3": ["thngs"], "18.2 -1.9 22.5": ["interplant"], "5.2 7.1 11.1": ["ziggy"], "11.0 27.5 16.3": ["counterpunchers"], "6.7 16.4 15.7": ["thready"], "0.3 5.8 10.3": ["disabilty"], "6.0 8.7 11.1": ["rescuees"], "12.8 3.8 11.6": ["producti"], "12.2 1.4 9.1": ["sharebrokers"], "7.0 28.2 28.4": ["longbeards"], "10.4 13.2 22.9": ["hoooo"], "6.6 9.3 23.0": ["whiskering"], "5.0 10.3 15.1": ["lavani"], "11.4 12.9 9.3": ["collectivised"], "8.7 17.8 18.6": ["submerse"], "16.9 0.7 16.1": ["millworks"], "25.9 14.0 36.8": ["pepperonis"], "13.9 10.6 7.7": ["trun"], "11.6 5.5 7.1": ["totalizer"], "7.9 15.0 11.7": ["oblations"], "1.8 -3.4 3.1": ["experi"], "-2.0 17.3 1.9": ["polemically"], "15.6 29.4 12.6": ["birddog"], "18.4 15.8 15.6": ["tholins"], "2.0 -2.5 10.8": ["reimbursment"], "7.3 13.9 10.0": ["volatilize"], "3.3 20.5 3.5": ["caviling"], "-5.3 8.9 6.5": ["grasstops"], "-3.1 5.4 9.4": ["nasality"], "7.3 10.0 9.2": ["akka"], "-4.5 6.8 6.1": ["nondriving"], "7.9 10.4 8.0": ["grapheme"], "-0.9 9.3 5.9": ["toidentify"], "18.9 16.0 18.2": ["gongfu"], "13.0 6.6 29.5": ["chowhound"], "-5.1 11.7 0.8": ["lability"], "15.8 11.4 14.3": ["flaka"], "4.6 18.9 6.7": ["booers"], "3.8 3.4 5.2": ["despit"], "7.2 13.9 14.9": ["bivvy"], "-0.3 -4.8 7.4": ["registation"], "-10.6 4.1 -1.1": ["dministration"], "14.2 7.2 11.9": ["furnance"], "9.2 19.9 5.4": ["charecter"], "3.0 0.1 13.3": ["homopolymer"], "6.8 -1.3 4.3": ["pingg"], "2.0 5.5 0.7": ["microsurgeon"], "13.9 16.6 18.4": ["minehunter"], "19.8 17.1 4.1": ["battleplan"], "17.8 15.0 22.3": ["uprighting"], "6.7 1.9 12.0": ["commexes"], "-2.1 5.2 0.8": ["socioemotional"], "5.2 5.3 -2.6": ["provisons"], "5.9 13.7 5.5": ["phonied"], "7.5 3.8 10.9": ["haciendo"], "14.1 -3.2 37.1": ["sealskins"], "2.0 4.3 6.5": ["cateos"], "3.3 16.7 2.5": ["enamor"], "15.3 0.8 45.3": ["hijiki"], "18.2 6.8 32.3": ["chappati"], "4.2 14.6 10.4": ["multitap"], "7.8 18.4 11.1": ["incedent"], "6.8 4.1 6.5": ["preimplantation"], "0.2 5.9 6.6": ["referrring"], "-6.0 21.4 14.6": ["recreationist"], "5.4 1.4 12.1": ["gites"], "-7.7 8.4 -2.6": ["thrity"], "-5.0 5.4 18.6": ["reweighing"], "9.6 2.3 8.6": ["norco"], "-1.2 20.7 0.5": ["relgion"], "0.1 9.8 13.5": ["gearset"], "13.3 15.8 26.7": ["sphagnum"], "6.3 17.0 12.8": ["macroscopically"], "14.2 16.3 24.5": ["deadfalls"], "-2.3 8.4 13.4": ["subluxed"], "6.1 10.2 15.7": ["unu"], "0.2 13.3 17.4": ["kori"], "-4.8 6.4 10.5": ["hopfully"], "14.8 9.3 10.6": ["gasholder"], "6.9 -1.1 1.6": ["hotspur"], "-1.6 6.0 3.4": ["cenvat"], "-3.8 29.4 2.4": ["selfdefense"], "4.0 17.1 11.7": ["disproportions"], "0.1 13.7 4.8": ["immovables"], "10.8 16.0 13.8": ["shamnesty"], "1.6 2.9 20.1": ["predominatly"], "10.1 17.5 9.2": ["omnia"], "8.3 19.1 25.9": ["sympatric"], "11.9 9.7 13.8": ["charpoys"], "7.5 8.5 8.7": ["khub"], "-0.3 13.5 4.6": ["baroreceptors"], "6.5 3.3 3.7": ["busies"], "16.4 10.3 12.2": ["disties"], "7.8 19.5 0.6": ["prate"], "9.9 19.7 12.0": ["strews"], "4.5 18.1 20.1": ["screwworm"], "6.1 11.8 11.2": ["courters"], "18.5 13.3 22.6": ["whizzer"], "9.6 6.8 9.1": ["fastbowler"], "11.2 15.9 10.4": ["gameplays"], "6.9 2.6 6.1": ["exepcted"], "-1.1 -0.4 4.3": ["rithmatic"], "7.5 0.3 4.5": ["expediate"], "8.4 13.6 8.9": ["mearly"], "0.2 24.1 5.3": ["cannoneer"], "24.0 -3.4 15.0": ["helter"], "8.5 7.6 15.8": ["shinbones"], "9.7 11.5 16.6": ["leftofwhat"], "6.9 13.2 12.4": ["grupetto"], "13.9 7.1 6.7": ["campagne"], "1.8 0.5 5.9": ["unbroadcast"], "6.7 12.4 32.5": ["cardamoms"], "7.8 1.1 -1.9": ["portofolio"], "6.3 24.5 13.0": ["moralizer"], "9.3 7.7 6.3": ["enti"], "6.3 7.1 6.8": ["concers"], "4.4 -10.3 8.9": ["willtake"], "4.2 1.4 14.1": ["marajuana"], "27.3 6.2 22.0": ["gasometer"], "3.4 1.2 20.7": ["leng"], "-4.3 21.4 -0.9": ["recced"], "4.6 16.5 13.4": ["condtion"], "5.3 4.9 24.6": ["subzi"], "9.3 10.8 2.5": ["noncarbon"], "4.7 8.5 -0.7": ["dormwear"], "-2.3 2.0 5.4": ["cholelithiasis"], "5.5 10.2 9.6": ["saccharification"], "2.5 9.5 1.2": ["experienc"], "10.3 8.5 9.1": ["buthe"], "0.5 6.6 0.6": ["alreday"], "17.6 14.0 11.8": ["keens"], "10.9 11.5 11.9": ["overdrives"], "4.0 8.2 8.9": ["throughfare"], "14.1 11.5 14.4": ["propitiatory"], "12.3 17.9 6.7": ["presbyterian"], "2.6 11.2 -4.8": ["satement"], "15.5 2.3 15.9": ["ewers"], "3.8 12.5 3.1": ["debaathification"], "16.9 21.0 24.5": ["tranquillized"], "3.7 -2.8 10.6": ["hadrah"], "2.9 0.1 -0.2": ["appea"], "22.9 8.7 15.5": ["escutcheons"], "-4.2 19.0 9.2": ["insaan"], "4.4 9.0 9.3": ["spaceflyer"], "-1.1 9.6 8.0": ["sideroad"], "16.0 5.7 -2.6": ["managament"], "0.9 14.2 15.3": ["congresscritters"], "12.6 2.4 11.5": ["demandfor"], "7.4 3.6 12.0": ["resorcinol"], "0.6 18.2 -4.3": ["neccesity"], "21.0 8.4 19.0": ["riverscape"], "7.2 5.5 -6.9": ["hasthe"], "-3.9 25.1 3.5": ["civilianize"], "0.4 6.9 12.1": ["canyoners"], "-0.5 12.8 5.1": ["ableism"], "8.2 19.2 9.2": ["blamelessly"], "-9.2 -4.7 8.2": ["microg"], "18.2 3.1 14.5": ["sofabed"], "7.6 18.3 12.5": ["windsprints"], "14.2 3.3 29.8": ["chantilly"], "7.5 -0.9 9.9": ["chevrolet"], "4.3 17.3 10.8": ["streches"], "14.1 9.5 -0.4": ["voltaic"], "4.3 3.6 16.2": ["resacas"], "19.8 18.2 18.0": ["serried"], "10.6 5.2 1.2": ["exergame"], "17.3 6.6 12.2": ["beatup"], "5.0 9.5 5.3": ["pocketability"], "11.9 10.5 27.3": ["limejuice"], "3.6 -5.7 -3.3": ["equivalant"], "2.9 13.7 17.3": ["barstaff"], "9.2 9.9 21.6": ["brac"], "-7.8 8.4 1.9": ["inhospital"], "4.4 16.2 14.3": ["chevyhotrod"], "4.8 22.6 4.9": ["extrodinary"], "-3.2 -0.7 0.3": ["thalassaemic"], "4.6 -1.9 -4.5": ["dicussing"], "10.3 0.3 28.5": ["tbsps"], "14.3 8.3 36.0": ["togarashi"], "4.7 11.9 8.5": ["sceptism"], "-6.1 10.1 -4.6": ["wirh"], "2.7 7.6 5.3": ["possibl"], "6.0 8.5 8.6": ["boxiness"], "0.2 5.1 8.7": ["standholders"], "6.3 5.1 13.6": ["guestimated"], "2.4 2.9 7.8": ["whereases"], "5.0 7.8 19.3": ["yabusame"], "15.4 15.5 16.2": ["paperlike"], "11.7 -0.7 19.2": ["crawfishermen"], "-11.8 11.3 1.8": ["signifigance"], "8.6 27.5 17.6": ["draenei"], "24.1 18.9 10.7": ["photosensor"], "12.7 -1.8 34.1": ["tortelli"], "7.1 10.3 2.1": ["corteges"], "1.2 14.7 9.6": ["retime"], "10.6 15.3 27.9": ["gnatcatcher"], "4.9 2.9 10.4": ["ohra"], "1.7 11.7 4.8": ["opeds"], "1.8 -1.3 9.7": ["threeweek"], "3.5 -3.5 2.6": ["evento"], "0.6 10.6 9.3": ["bowings"], "-2.0 17.7 10.6": ["numerosity"], "2.9 17.9 5.9": ["citzen"], "9.5 15.2 -0.9": ["naissance"], "7.5 6.5 10.0": ["vacuolar"], "-3.6 8.2 7.9": ["consistories"], "-2.6 21.7 5.8": ["zapatistas"], "2.4 7.8 9.8": ["alst"], "5.3 11.8 13.5": ["nonsustainable"], "4.6 10.7 23.5": ["vulgare"], "8.5 21.0 4.7": ["crossbucks"], "5.1 11.2 30.9": ["kho"], "1.8 11.6 9.8": ["alones"], "4.9 15.0 17.1": ["pseudogout"], "4.7 12.0 9.8": ["bukan"], "-0.7 8.2 8.8": ["bhala"], "-0.4 11.5 10.2": ["tracheitis"], "20.2 16.4 28.6": ["medlar"], "13.3 10.4 -0.0": ["telerobotics"], "34.0 11.9 22.2": ["snowwoman"], "2.6 19.1 1.5": ["transnationally"], "9.7 11.5 4.3": ["vitalise"], "-2.0 9.4 2.8": ["ochratoxin"], "14.6 2.3 13.2": ["choons"], "-1.6 9.9 6.3": ["deadband"], "13.6 13.3 1.8": ["fetishise"], "4.7 -1.3 -5.5": ["uncouples"], "-0.2 14.6 9.4": ["multiphoton"], "-4.7 10.3 12.8": ["strobilurins"], "-7.3 5.7 11.9": ["amm"], "21.1 23.4 24.7": ["aargh"], "-0.0 4.3 13.4": ["palkhi"], "3.3 19.0 4.9": ["quasiparticle"], "7.8 9.4 3.6": ["injested"], "-1.1 14.3 17.4": ["muaythai"], "2.5 26.4 4.5": ["priciples"], "3.1 10.2 1.6": ["psiphon"], "12.5 29.1 13.2": ["flechette"], "-0.4 7.0 4.5": ["releveraging"], "9.7 11.5 19.8": ["cann"], "-0.7 2.8 2.7": ["aggiornamento"], "11.7 10.7 20.0": ["muckle"], "5.5 1.2 9.2": ["gira"], "6.7 0.6 -1.7": ["derzeit"], "11.3 18.2 9.9": ["identies"], "18.2 7.1 8.2": ["spooler"], "-3.6 7.1 4.8": ["determin"], "8.0 -4.4 -5.3": ["exlcusive"], "20.0 17.4 14.3": ["frontwards"], "12.0 4.1 18.2": ["windswell"], "-8.1 12.5 2.9": ["propounder"], "6.4 4.0 29.5": ["papadum"], "4.3 21.5 2.6": ["regretably"], "6.7 20.1 10.2": ["snottily"], "2.1 8.9 5.2": ["linewidths"], "-3.3 23.1 6.4": ["countertransference"], "3.8 17.4 8.1": ["strenghth"], "2.5 17.1 7.0": ["lolol"], "2.9 10.8 10.0": ["tonsillar"], "19.4 12.3 25.9": ["juicehead"], "13.6 4.4 9.9": ["geotargeted"], "11.6 17.0 11.1": ["slashdotted"], "8.9 13.2 20.7": ["postups"], "6.3 7.7 1.4": ["beneift"], "17.9 12.8 17.9": ["honeylocust"], "13.1 12.2 13.3": ["debri"], "-1.6 1.8 4.4": ["hyperlipidaemia"], "10.1 17.6 8.6": ["kibbitz"], "0.0 7.2 7.8": ["fami"], "-2.1 2.3 6.8": ["metaanalysis"], "1.7 7.3 10.6": ["prevalant"], "-3.8 7.1 -7.1": ["metioned"], "7.4 27.8 14.6": ["unexplorable"], "22.4 5.1 16.7": ["cornershop"], "4.8 -0.8 5.6": ["sportsfields"], "6.7 10.7 8.7": ["educed"], "9.1 19.0 18.9": ["cummin"], "0.6 2.4 7.9": ["crammer"], "-0.7 -1.2 7.0": ["pentostatin"], "1.0 8.9 -2.9": ["urbanistic"], "4.7 18.4 22.4": ["bdelloids"], "12.8 19.6 29.8": ["porpoising"], "9.3 13.1 15.7": ["esle"], "6.9 11.3 13.8": ["bruisin"], "3.3 10.4 17.7": ["coper"], "0.1 5.3 -1.1": ["deontology"], "1.2 6.4 8.3": ["collge"], "-1.1 9.7 8.6": ["enkephalins"], "12.1 9.8 2.4": ["wonderkids"], "5.0 3.8 12.8": ["conside"], "14.3 9.9 8.2": ["horsie"], "1.1 10.8 7.2": ["anticorrosive"], "-4.1 8.5 5.6": ["fand"], "27.3 18.3 22.1": ["hassock"], "3.7 23.3 7.2": ["carying"], "14.3 22.5 10.5": ["duststorms"], "16.9 15.3 7.2": ["radiowave"], "11.2 18.3 20.9": ["photinia"], "3.4 -6.8 15.5": ["gew"], "8.1 11.0 14.5": ["variogram"], "-1.5 6.4 1.1": ["chastizing"], "3.4 8.7 16.3": ["nephron"], "3.4 3.0 14.2": ["clare"], "17.3 5.0 21.5": ["doggystyle"], "-1.8 24.3 4.4": ["ultimatly"], "14.3 18.7 5.5": ["internauts"], "-1.4 4.9 6.9": ["undercollateralized"], "21.3 10.6 19.9": ["pongy"], "8.7 -0.3 11.5": ["isomaltulose"], "-2.2 8.1 -1.9": ["quires"], "16.5 27.3 19.1": ["yanqui"], "15.2 11.4 13.0": ["shinin"], "13.0 3.8 0.1": ["otcbb"], "23.7 12.1 15.3": ["slippered"], "-0.7 14.5 10.3": ["arguida"], "6.3 10.7 9.0": ["effectivness"], "6.2 10.0 7.8": ["funloving"], "9.8 4.5 -0.1": ["lcoal"], "2.4 -5.1 8.4": ["dium"], "12.4 7.1 20.3": ["gnus"], "8.0 11.4 4.2": ["recomposing"], "8.7 9.9 13.8": ["descenders"], "10.3 -3.6 10.2": ["suppliment"], "16.9 11.0 6.1": ["jackeroo"], "8.7 8.9 7.3": ["melodiousness"], "14.6 13.8 10.4": ["disembowelments"], "6.3 8.2 3.7": ["hestitant"], "-3.6 7.3 5.2": ["diffe"], "10.4 8.1 16.2": ["acrosome"], "-2.1 7.8 8.5": ["caree"], "21.3 2.2 12.2": ["soundsystems"], "14.3 10.2 28.4": ["firebush"], "19.1 16.7 13.6": ["scaped"], "4.6 3.0 10.9": ["heptachlor"], "5.7 5.6 4.5": ["opcodes"], "-8.8 7.3 -4.4": ["offerees"], "9.5 14.5 33.4": ["trencherman"], "0.4 8.4 -0.1": ["rebbes"], "5.1 4.6 16.1": ["chori"], "8.0 13.2 7.7": ["slanguage"], "5.7 -1.4 14.7": ["deferreds"], "4.4 -1.7 18.3": ["carey"], "-9.0 5.2 3.0": ["cocaptains"], "-0.2 18.6 16.1": ["receiveth"], "2.1 9.3 6.7": ["supermoms"], "10.7 28.3 9.2": ["sidescroller"], "13.7 9.4 9.9": ["scoopage"], "21.3 13.7 16.3": ["strutter"], "14.6 -1.7 -1.5": ["sents"], "19.8 27.1 16.0": ["gorey"], "9.7 16.9 10.0": ["sootiest"], "-7.1 8.3 4.8": ["succint"], "6.9 2.6 -2.7": ["autodrome"], "7.2 3.8 9.9": ["dru"], "6.9 9.8 -2.4": ["afree"], "1.4 10.4 20.7": ["standability"], "2.5 11.3 7.4": ["inferencing"], "20.9 21.9 11.4": ["corperate"], "4.7 15.6 14.6": ["overtrade"], "-3.1 7.1 6.3": ["catheterize"], "-0.5 3.5 8.9": ["walima"], "-0.9 -0.2 6.6": ["shon"], "5.8 14.4 13.3": ["kylie"], "7.9 9.6 12.5": ["shapefiles"], "11.3 14.2 1.5": ["wthout"], "13.5 14.0 26.9": ["redbay"], "2.8 7.1 3.2": ["reponding"], "-2.5 0.7 14.1": ["ngang"], "19.5 18.8 7.6": ["berzerk"], "6.6 -4.6 20.7": ["kati"], "4.6 -4.9 5.8": ["scientifique"], "7.9 5.7 3.8": ["casopitant"], "-0.6 10.8 13.4": ["kenpo"], "-2.0 12.5 2.5": ["matc"], "9.8 15.6 13.4": ["yantra"], "10.4 21.4 17.0": ["noblewomen"], "-7.0 11.9 13.0": ["airsheds"], "8.8 10.1 6.6": ["guitaring"], "6.3 8.9 16.9": ["shal"], "-10.1 3.6 -1.4": ["assurred"], "6.2 -1.3 8.5": ["chanteur"], "12.3 -0.1 22.9": ["reina"], "-0.6 3.5 -2.8": ["arealso"], "14.3 6.6 12.1": ["overfloweth"], "0.3 6.6 13.3": ["arrivers"], "5.6 5.3 8.2": ["dermatosis"], "-5.7 8.5 8.3": ["disenrolling"], "-0.6 18.7 7.8": ["outprocessing"], "10.2 11.3 5.2": ["demutualising"], "-2.9 -0.6 0.5": ["thecapital"], "18.3 26.0 11.6": ["nerdgasm"], "-0.4 3.8 -1.9": ["expereinced"], "0.1 18.7 4.0": ["plagiaristic"], "4.9 1.6 11.4": ["casse"], "5.4 12.4 14.6": ["sooners"], "11.5 8.9 8.7": ["bordertown"], "-1.5 -4.9 -1.5": ["availableat"], "3.6 -0.6 7.9": ["teeshirts"], "3.9 9.3 18.8": ["floorcloths"], "13.3 13.5 -1.8": ["socities"], "19.7 11.3 27.8": ["therizinosaurs"], "18.1 13.7 18.2": ["mashie"], "4.6 11.5 40.7": ["catfishermen"], "7.2 19.8 20.3": ["noninfected"], "9.7 9.8 29.8": ["prebaked"], "24.8 8.4 10.1": ["radiotelescope"], "0.3 1.5 4.2": ["titrations"], "17.3 2.4 16.7": ["harked"], "1.1 15.0 10.3": ["steric"], "11.4 9.9 10.8": ["aspirers"], "1.9 25.8 6.8": ["transnationalist"], "13.4 -0.1 34.1": ["frito"], "-6.1 7.5 4.9": ["revictimization"], "11.0 12.5 14.1": ["insipidity"], "-9.9 4.3 0.5": ["themeeting"], "11.8 35.7 10.8": ["corpocracy"], "8.9 5.6 2.2": ["gratia"], "8.8 -2.9 9.2": ["peoria"], "30.0 22.2 17.4": ["underseas"], "-2.4 11.8 -0.9": ["xxxxxxxx"], "-8.8 6.6 2.3": ["oversign"], "1.3 7.3 4.6": ["bicameralism"], "9.6 11.0 9.8": ["knuckleballing"], "12.3 4.1 2.0": ["fashionisto"], "2.5 9.0 5.3": ["kanun"], "6.4 2.7 28.6": ["pastillas"], "-6.9 21.4 4.0": ["trangressions"], "12.2 4.6 20.7": ["etagere"], "1.4 19.3 9.9": ["peson"], "16.4 10.0 -1.3": ["repossessor"], "-7.1 16.8 10.1": ["unpredicatable"], "-1.1 2.2 10.6": ["urothelium"], "10.2 0.9 5.8": ["ebuild"], "4.4 3.2 8.7": ["outtage"], "0.4 5.3 4.5": ["sankalp"], "5.0 4.0 17.7": ["burred"], "9.6 6.8 23.6": ["pizzelle"], "10.8 14.5 17.0": ["hemerocallis"], "14.2 15.1 19.2": ["suborder"], "21.2 9.2 20.4": ["megafarm"], "17.8 26.1 15.1": ["celts"], "10.8 -4.9 31.8": ["torchon"], "3.7 31.3 9.8": ["kurds"], "24.1 8.4 9.3": ["crossholdings"], "0.7 15.9 8.4": ["interupting"], "3.6 19.0 5.0": ["electoralism"], "11.7 22.9 12.6": ["hubristically"], "0.6 1.1 10.5": ["reinswoman"], "16.0 26.7 18.1": ["overbreed"], "7.1 -0.7 11.8": ["nonwage"], "11.5 20.8 11.9": ["prehistorical"], "10.0 -0.2 8.0": ["twnhm"], "4.3 15.2 15.4": ["genitive"], "3.4 -2.7 -3.8": ["websit"], "-6.1 4.0 0.1": ["isokinetic"], "1.0 6.1 8.4": ["ryeol"], "3.4 19.5 14.5": ["noncontagious"], "5.0 8.3 6.3": ["temperately"], "15.5 -0.3 6.0": ["soln"], "2.7 12.3 6.0": ["headcases"], "3.7 4.3 4.2": ["erste"], "18.3 7.5 16.4": ["snackbar"], "-2.0 3.3 -3.5": ["confirme"], "12.0 11.3 8.5": ["expatriots"], "-5.0 3.6 6.4": ["azoospermia"], "-3.8 12.7 15.9": ["fallows"], "5.3 4.3 14.4": ["ftit"], "14.6 4.1 15.2": ["negrito"], "16.5 11.9 36.1": ["finless"], "9.5 11.2 2.4": ["counterstatement"], "9.7 14.3 25.5": ["kingbirds"], "7.3 15.8 7.5": ["tattlers"], "2.4 4.7 11.7": ["esterase"], "3.1 12.3 14.9": ["shrinkages"], "16.1 4.9 31.2": ["samoosas"], "10.0 2.9 9.1": ["cinematheques"], "12.8 16.7 16.1": ["fuddle"], "-0.8 6.2 9.7": ["sekolah"], "7.1 50.0 2.3": ["counterfire"], "3.1 4.8 19.1": ["sobra"], "18.5 7.9 10.2": ["pogoed"], "9.2 10.3 9.7": ["pharmacophore"], "15.3 22.9 19.0": ["luchadore"], "8.3 2.9 8.0": ["repreive"], "4.4 4.0 19.8": ["ceci"], "8.5 15.3 5.8": ["reflectometry"], "0.9 1.2 12.9": ["magpa"], "-4.4 3.8 7.8": ["polyuria"], "7.2 3.1 12.2": ["mense"], "9.9 10.5 14.6": ["unclamped"], "13.3 12.1 23.7": ["groundsel"], "8.2 13.4 16.8": ["velit"], "9.5 8.2 -0.6": ["ministery"], "11.5 14.0 11.0": ["ridiculus"], "-3.4 15.6 5.4": ["inappropiate"], "13.3 10.8 27.6": ["underbaked"], "1.4 0.1 6.8": ["pms"], "19.9 1.1 25.7": ["beavertail"], "17.5 30.5 16.0": ["doodlebugs"], "1.6 11.4 14.6": ["landscapist"], "-7.4 12.2 -7.5": ["artice"], "-4.8 6.6 -5.2": ["compliants"], "-4.3 -5.9 -2.1": ["wonthe"], "17.9 -0.3 29.4": ["fillo"], "16.6 10.4 5.1": ["teekid"], "-4.5 -3.7 4.0": ["sportpersons"], "-2.4 -0.1 0.5": ["beco"], "3.2 4.8 -6.9": ["hangared"], "-0.2 15.7 3.8": ["gouvernement"], "-3.6 9.1 10.0": ["nonpharmacological"], "4.0 7.3 13.2": ["frailness"], "13.3 30.4 7.9": ["backslider"], "4.2 -3.9 8.5": ["insome"], "1.7 1.0 12.0": ["rhinoplasties"], "10.1 21.7 14.0": ["bringeth"], "12.2 7.6 22.1": ["moma"], "3.3 -13.7 5.6": ["todayin"], "8.6 -1.8 5.0": ["estore"], "13.9 18.9 18.7": ["ravishment"], "10.5 1.7 30.9": ["kapenta"], "3.6 9.5 10.5": ["convienient"], "5.0 5.5 -1.0": ["authencity"], "7.4 -1.0 35.6": ["redband"], "9.1 13.6 50.1": ["sandies"], "7.0 1.3 13.6": ["specialevents"], "0.9 18.5 8.7": ["noncommunicative"], "5.8 9.0 19.3": ["tuf"], "-0.1 7.2 11.5": ["macedonia"], "16.9 16.2 6.4": ["unviewable"], "5.7 14.8 18.5": ["chup"], "7.1 15.1 17.1": ["unbelivable"], "-2.5 9.0 13.2": ["connor"], "10.2 3.9 24.1": ["banksias"], "12.3 30.2 11.5": ["hegemonists"], "19.8 17.0 9.7": ["junkpile"], "10.7 7.3 13.3": ["restimulate"], "8.1 7.2 5.5": ["untick"], "3.6 5.8 7.3": ["vectorscope"], "8.7 6.7 7.2": ["freee"], "1.5 21.4 17.1": ["savasana"], "9.3 14.9 8.6": ["outthere"], "15.7 8.2 13.4": ["ogni"], "15.0 14.0 32.5": ["snell"], "3.2 5.3 12.3": ["punchiest"], "4.9 25.2 -1.0": ["denazification"], "3.0 8.7 8.1": ["streetism"], "-1.6 -2.8 0.4": ["adminis"], "8.2 21.0 7.2": ["outshouted"], "6.0 11.5 9.5": ["schlepp"], "12.6 9.9 37.8": ["stirfry"], "6.2 10.0 16.6": ["grandis"], "4.7 0.4 1.3": ["polewinner"], "6.1 -1.4 18.0": ["concha"], "11.0 11.7 4.6": ["mythbuster"], "5.6 14.3 8.3": ["unregarded"], "6.8 9.8 27.0": ["babaganoush"], "15.9 15.1 15.5": ["bludge"], "4.1 0.6 13.2": ["rackmountable"], "16.2 15.7 28.6": ["northwester"], "5.3 -1.0 9.8": ["sugg"], "2.5 10.7 28.9": ["plunkers"], "2.9 9.3 14.7": ["whateva"], "3.8 5.6 8.8": ["ospemifene"], "8.8 21.3 12.6": ["lonliness"], "2.0 16.2 4.9": ["hyberbole"], "-2.0 10.0 1.4": ["eulogistic"], "-0.4 8.0 9.7": ["ubiquitylation"], "-1.8 -2.5 7.8": ["reair"], "8.2 15.0 16.0": ["miscon"], "12.7 3.2 2.7": ["roadtest"], "-1.6 17.2 10.4": ["plotz"], "4.0 23.1 17.2": ["sehwag"], "0.8 20.3 6.5": ["intellectualization"], "0.2 6.3 12.7": ["postpractice"], "19.5 4.4 14.9": ["pelmets"], "6.6 2.4 -2.2": ["softline"], "-0.1 8.7 9.1": ["moncler"], "10.9 10.1 16.0": ["micropores"], "3.5 -2.9 0.8": ["macrocyclic"], "3.1 2.7 9.0": ["benzodiazopines"], "12.3 5.3 14.3": ["cartoneros"], "1.8 -3.4 -0.3": ["newsboard"], "5.6 4.5 -2.9": ["therest"], "15.0 5.3 6.0": ["itv"], "8.0 4.7 0.7": ["responisble"], "8.1 1.1 9.7": ["ironers"], "6.2 10.4 13.6": ["stalkings"], "5.0 3.4 2.2": ["antiapartheid"], "3.4 4.1 7.1": ["degression"], "3.5 11.1 7.4": ["nonconstitutional"], "-4.4 -1.6 4.8": ["microtia"], "4.0 0.0 14.8": ["bele"], "2.6 4.2 19.4": ["quaich"], "16.5 11.5 15.0": ["towtruck"], "1.6 14.8 4.7": ["yatri"], "0.6 11.0 -0.4": ["scrutinization"], "13.0 19.3 16.7": ["huarango"], "0.3 14.0 7.0": ["apoint"], "6.6 15.1 13.3": ["mosley"], "16.6 18.4 15.6": ["rainsuits"], "-2.3 -6.0 5.4": ["cers"], "8.9 20.9 8.9": ["atention"], "21.0 9.6 14.3": ["skirling"], "2.1 16.7 14.2": ["germophobia"], "17.5 13.4 17.7": ["beetling"], "-0.1 22.3 1.6": ["politicide"], "-5.2 1.5 1.7": ["qnotes"], "8.1 18.8 11.9": ["sumoylation"], "8.5 15.2 9.2": ["sumthing"], "18.0 8.5 10.0": ["panjandrum"], "1.8 -0.7 6.2": ["idursulfase"], "15.8 3.6 -0.3": ["onced"], "6.6 13.6 10.9": ["regifts", "sysprep"], "25.4 19.1 19.3": ["longship"], "3.4 7.5 16.0": ["deskmate"], "8.3 11.8 5.0": ["twitterings"], "4.7 2.8 2.4": ["dualband"], "11.5 -0.6 13.3": ["companyais"], "23.4 7.7 7.0": ["pinboard"], "8.8 -4.0 4.7": ["biorenewables"], "6.8 17.8 2.0": ["geolocate"], "24.8 0.1 13.6": ["dealie"], "5.1 26.0 -3.3": ["tyrannic"], "16.3 9.6 11.8": ["multispeed"], "8.0 1.5 15.7": ["kev"], "13.5 6.5 7.7": ["piezometers"], "2.2 6.8 9.0": ["zam"], "7.8 3.0 26.0": ["gardein"], "10.6 3.8 37.6": ["pernil"], "-2.0 1.8 1.4": ["clincs"], "-2.8 28.1 0.5": ["confidents"], "-11.3 -2.2 -5.2": ["disciplinaries"], "16.0 8.3 9.0": ["geolocated"], "6.9 10.5 21.3": ["helminth"], "7.3 -0.6 -3.1": ["telecenter"], "2.3 11.4 15.7": ["patterson"], "3.9 12.1 7.8": ["extravert"], "25.9 15.3 18.4": ["teddybear"], "-3.4 14.2 9.1": ["renominations"], "5.8 9.0 3.6": ["kazaa"], "5.3 12.3 17.2": ["fagging"], "20.9 14.8 18.2": ["bombes"], "-2.7 4.4 8.3": ["caspofungin"], "0.4 6.9 14.8": ["talathi"], "-2.1 11.9 14.3": ["sitwasyon"], "3.3 15.5 8.5": ["codebases"], "7.5 29.1 12.2": ["speciousness"], "-6.4 16.7 16.1": ["nodulation"], "7.2 4.2 0.6": ["domiciliation"], "13.0 9.9 19.8": ["breezeless"], "-6.7 20.9 -3.3": ["inactiveness"], "2.0 16.3 16.2": ["recrystallized"], "9.6 4.2 16.0": ["fios"], "25.8 11.3 17.3": ["rubberbands"], "8.9 17.3 8.8": ["imapct"], "4.7 4.6 17.7": ["spreadability"], "-0.7 8.1 10.7": ["geraniol"], "-0.8 13.1 2.6": ["supprised"], "12.7 12.0 7.7": ["toend"], "6.0 11.5 13.8": ["synopsize"], "1.7 -3.0 8.3": ["fost"], "3.5 12.4 6.4": ["bluepulse"], "7.8 14.3 15.5": ["oohh"], "15.1 15.8 5.7": ["replacable"], "3.5 -0.8 42.0": ["galunggong"], "6.8 1.3 12.9": ["gwasanaethau"], "1.0 8.0 7.0": ["misutilised"], "1.1 -1.7 3.4": ["toaddress"], "3.8 22.1 4.4": ["misapprehend"], "7.4 5.5 3.3": ["vagotomy"], "-3.3 10.2 6.4": ["triages"], "13.0 9.8 9.0": ["flappable"], "12.4 2.4 15.7": ["lois"], "-0.9 7.2 -2.6": ["laryngoscopy"], "0.9 4.7 5.0": ["chronotherapy"], "17.8 21.5 4.6": ["flackery"], "11.7 10.5 30.2": ["gurgitators"], "8.6 3.1 18.8": ["breaky"], "8.6 8.1 15.9": ["nsima"], "15.2 5.4 1.8": ["owers"], "12.8 9.2 18.4": ["juss"], "6.6 16.5 20.0": ["shipfitter"], "-2.7 17.0 1.7": ["urotrauma"], "4.8 5.3 0.6": ["scholl"], "-0.3 14.1 5.7": ["appriciate"], "11.6 3.8 18.4": ["reglazed"], "-8.5 3.8 -5.7": ["forenames"], "-0.1 -6.4 -0.1": ["andunder"], "0.5 6.2 10.1": ["tetany"], "13.6 12.6 11.5": ["adulthoods"], "11.2 8.2 29.6": ["pennywort"], "3.2 4.7 18.0": ["gifty"], "0.3 5.1 10.0": ["paraganglioma"], "5.6 43.4 5.2": ["terorists"], "16.8 15.7 16.7": ["toreros"], "11.0 0.9 4.1": ["doha"], "6.4 21.3 8.7": ["overstrain"], "6.1 3.0 26.3": ["mailboat"], "12.6 8.3 12.5": ["cyano"], "5.3 7.8 4.6": ["metabolization"], "-0.3 5.5 6.3": ["iki"], "14.9 12.3 19.1": ["unsmooth"], "10.5 12.8 7.1": ["mim"], "12.2 14.6 4.7": ["promissed"], "11.2 3.5 5.8": ["raggae"], "11.8 13.1 3.0": ["emblematically"], "1.0 5.8 3.9": ["furher"], "16.2 10.3 16.9": ["pachislot"], "12.8 9.1 8.6": ["hardcoat"], "14.0 11.5 20.5": ["megaship"], "5.7 6.1 17.0": ["rhum"], "-6.1 -1.5 19.7": ["birdwalk"], "1.2 10.5 18.0": ["gomes"], "2.1 14.6 10.3": ["fringsters"], "8.6 -4.8 4.0": ["servicios"], "7.0 7.5 32.8": ["appams"], "-3.2 1.8 3.4": ["nonplaying"], "0.7 10.2 14.0": ["gametocytes"], "10.9 1.2 7.6": ["taximeter"], "4.7 6.6 16.6": ["resulta"], "3.2 7.3 -1.0": ["permision"], "2.6 8.6 -5.3": ["lawers"], "13.5 15.6 14.0": ["gothed"], "-6.8 8.6 -0.3": ["querry"], "8.0 14.5 6.2": ["activiated"], "6.9 8.0 13.5": ["elimated"], "9.0 2.7 9.6": ["tostart"], "7.1 1.2 9.8": ["syzygy"], "13.7 9.5 3.4": ["chantings"], "8.9 21.5 14.0": ["agon"], "9.9 3.5 10.4": ["repolish"], "0.9 7.1 7.7": ["olarak"], "5.1 4.3 9.4": ["cosas"], "7.5 -5.6 4.0": ["hydrochlorofluorocarbons"], "4.3 15.5 -1.1": ["arraigns"], "7.2 1.6 9.6": ["ovat"], "5.3 10.1 5.6": ["dort"], "-4.8 1.7 1.1": ["convenorship"], "9.6 21.3 6.5": ["ironfisted"], "6.2 8.3 10.3": ["becausethey"], "6.0 1.4 6.4": ["suspensive"], "17.1 18.1 12.0": ["hypodermics"], "12.7 5.5 14.5": ["mettre"], "7.7 16.6 10.9": ["philisophical"], "9.5 12.4 3.3": ["geomarketing"], "0.9 -7.0 2.8": ["faci"], "7.0 3.9 13.7": ["adown"], "9.9 20.2 28.6": ["corvid"], "4.9 -12.3 7.3": ["evocos"], "15.0 10.4 5.7": ["nomadically"], "8.0 8.1 2.8": ["obfuscators"], "3.7 8.6 9.1": ["mininotebooks"], "6.6 10.6 7.2": ["hapened"], "8.4 11.3 9.7": ["paen"], "13.6 10.1 19.1": ["shoegazey"], "-0.3 10.9 7.5": ["protonated"], "10.1 20.0 14.0": ["enviorment"], "-3.0 5.8 27.8": ["amarone"], "10.8 12.7 15.4": ["reabsorbs"], "14.6 -2.2 34.2": ["lilikoi"], "-1.2 12.3 -1.1": ["hewill"], "10.1 1.7 16.7": ["platy"], "-3.2 7.7 18.0": ["rine"], "17.6 6.5 12.4": ["topsiders"], "-4.2 -3.4 1.1": ["nondaily"], "12.7 -3.8 12.6": ["friesian"], "5.3 9.9 11.3": ["schnitzeling"], "0.8 3.6 5.2": ["interestrate"], "19.4 9.3 11.8": ["rickrolling"], "6.7 17.3 33.2": ["surfline"], "22.4 0.2 12.6": ["laceless"], "21.9 10.0 26.2": ["choccy"], "3.1 -10.2 5.9": ["orr"], "1.3 21.7 5.7": ["shouldnot"], "6.4 -1.8 16.9": ["bouchon"], "-1.1 1.9 14.0": ["sasakyan"], "-4.3 -4.4 -1.1": ["deffered"], "0.9 5.3 0.8": ["sestamibi"], "12.5 11.8 19.4": ["nanoclays"], "8.4 21.7 9.5": ["plussed"], "16.3 5.5 17.7": ["washday"], "16.6 11.2 29.0": ["floatie"], "2.2 24.3 1.8": ["staunchness"], "8.4 14.4 10.0": ["retoric"], "11.5 32.1 15.1": ["battlestar"], "17.7 9.4 39.4": ["devein"], "4.9 10.7 3.0": ["divisonal"], "4.3 11.4 13.4": ["calvin"], "8.9 8.1 32.5": ["hubbard"], "7.1 13.0 9.2": ["vapidness"], "5.8 2.6 4.9": ["trigerred"], "8.1 14.4 16.3": ["springback"], "16.6 19.3 15.8": ["pudenda"], "14.5 8.1 25.4": ["lapin"], "-0.4 13.0 8.8": ["logfile"], "10.4 13.0 21.1": ["repens"], "1.7 -4.2 7.0": ["playcentres"], "4.8 10.0 14.3": ["chorten"], "-2.4 3.3 15.4": ["dagdag"], "6.7 27.6 0.6": ["surive"], "-0.6 19.4 12.8": ["poolees"], "11.9 0.8 2.2": ["productos"], "8.0 -4.9 5.1": ["suisse"], "-0.7 8.2 7.3": ["queenmother"], "-5.1 8.4 14.4": ["sinasabing"], "-3.4 -0.7 4.1": ["inhome"], "4.8 5.6 9.4": ["reinstill"], "7.1 5.5 2.1": ["overprescription"], "4.6 -2.3 5.2": ["cerca"], "9.5 23.2 10.2": ["chemtrail"], "11.1 11.4 14.8": ["booboos"], "8.7 8.6 11.4": ["boooo"], "9.1 17.7 6.4": ["hackerspace"], "8.5 12.5 20.9": ["wildife"], "5.7 0.4 8.1": ["hydrocephaly"], "0.6 6.2 11.5": ["karapatan"], "6.1 10.6 14.0": ["varius"], "20.7 21.0 12.1": ["unclimbable"], "12.1 23.0 5.0": ["quagmired"], "1.3 17.9 5.9": ["extenuated"], "7.8 11.5 14.5": ["mbakst"], "9.9 -3.3 0.4": ["switchless"], "2.5 6.7 11.7": ["justo"], "10.8 6.1 8.9": ["formamide"], "10.0 18.4 10.4": ["intracacies"], "6.2 3.9 3.6": ["grails"], "9.2 8.3 16.5": ["urbanizes"], "-5.6 20.7 0.7": ["nonanswer"], "7.4 32.3 18.1": ["thumos"], "2.5 4.3 2.4": ["critcized"], "9.7 21.5 17.8": ["outcompetes"], "20.8 8.6 19.1": ["undercrackers"], "-1.3 13.1 -7.1": ["examplary"], "7.8 12.6 14.1": ["princeofwheels"], "7.2 42.0 -1.0": ["terrrorist"], "4.3 10.7 17.8": ["neophobia"], "12.6 20.0 19.2": ["batton"], "24.0 34.7 18.6": ["buckler"], "9.5 26.7 6.2": ["imperialisms"], "2.3 11.3 10.2": ["stereographer"], "12.4 -2.0 7.0": ["extraordinaires"], "15.3 0.6 7.0": ["geomarket"], "-3.9 2.3 1.3": ["beconsidered"], "11.8 5.4 20.5": ["whoppin"], "14.4 8.4 12.8": ["censorhip"], "8.1 9.6 6.5": ["heartstopper"], "3.3 15.6 9.6": ["upar"], "3.3 12.2 16.5": ["zees"], "6.6 20.1 18.5": ["swordswoman"], "19.0 14.2 49.1": ["spawner"], "5.5 14.6 8.8": ["rubish"], "9.6 3.9 8.6": ["repackagers"], "10.2 8.7 22.3": ["broadtail"], "12.6 5.8 16.9": ["hifalutin"], "14.4 12.8 9.7": ["lovie"], "3.7 9.1 7.4": ["figurer"], "16.0 4.6 28.7": ["buko"], "0.7 6.6 2.1": ["mla"], "13.1 13.5 5.0": ["phonautograph"], "12.5 15.4 7.9": ["triangulations"], "11.2 15.5 19.8": ["pinestraw"], "1.3 14.5 17.6": ["steph"], "17.6 14.6 11.6": ["apocryphally"], "4.8 0.6 17.2": ["cattlefeed"], "12.5 16.2 14.0": ["martinets"], "8.8 14.6 2.3": ["bnp"], "-1.3 4.1 5.8": ["guarantied"], "1.7 11.4 3.4": ["handcyclists"], "17.9 9.5 17.9": ["hepcats"], "-7.3 4.5 5.0": ["acitretin"], "5.5 16.8 11.3": ["uninterest"], "13.1 10.0 9.0": ["cirlce"], "2.7 4.4 9.1": ["libres"], "-2.3 7.2 -2.9": ["ihrem"], "11.2 11.8 24.5": ["penicillium"], "3.0 1.2 4.7": ["racebikes"], "3.5 7.7 17.8": ["payne"], "12.3 5.9 14.2": ["rollicks"], "-8.4 8.9 -3.0": ["aninterview"], "3.0 8.0 3.2": ["compaints"], "13.8 16.1 19.6": ["bippy"], "3.4 7.3 7.8": ["flowergirls"], "-4.7 28.7 11.3": ["contraries"], "3.2 5.2 4.8": ["ccess"], "6.8 34.6 11.4": ["insulter"], "-3.1 0.4 5.5": ["chondral"], "14.7 20.4 13.4": ["orneriest"], "20.9 17.1 11.5": ["phonier"], "8.0 6.0 2.0": ["notorius"], "18.9 18.2 14.0": ["fistfighting"], "10.5 7.7 18.9": ["tuberoses"], "6.2 14.8 17.6": ["jeter"], "2.2 11.5 20.1": ["shirazes"], "3.2 9.0 11.6": ["raveled"], "8.0 2.9 6.7": ["superjail"], "26.3 9.0 22.0": ["lilos"], "6.9 12.1 9.8": ["cutdowns"], "7.9 -11.4 8.6": ["anaverage"], "18.5 8.2 11.9": ["skylighted"], "3.9 3.2 4.1": ["unten"], "5.1 5.7 1.7": ["metaxalone"], "11.4 -1.2 9.0": ["superbright"], "14.1 -2.6 18.6": ["wormeries"], "9.5 3.3 11.5": ["lightwelterweight"], "13.4 36.3 9.9": ["miniguns"], "8.9 7.0 14.2": ["whackings"], "8.8 5.1 13.5": ["bodylines"], "-2.9 4.2 3.8": ["basketall"], "4.2 -0.3 6.2": ["epigenomes"], "15.5 9.3 14.1": ["wildnerness"], "8.4 16.0 1.2": ["autarchy"], "12.4 9.5 9.1": ["weee"], "19.3 20.5 32.4": ["chafers"], "-2.3 10.7 7.5": ["cyberharassment"], "-1.6 20.6 15.9": ["improvidence"], "7.8 4.1 15.3": ["metamphetamine"], "1.4 5.5 2.3": ["contes"], "15.3 9.5 12.8": ["caparisoned"], "-0.0 13.8 10.9": ["limonoids"], "4.2 10.7 10.5": ["haling"], "3.1 11.9 -1.6": ["khalid"], "5.5 5.0 5.4": ["ecotherapy"], "5.7 6.8 8.8": ["fieriness"], "3.0 -0.0 5.0": ["zyprexa"], "10.6 6.7 5.5": ["midtower"], "-2.3 5.8 14.4": ["davidson"], "6.0 20.6 1.7": ["chnage"], "11.2 8.0 14.0": ["nanofluidics"], "11.1 16.6 6.5": ["dumbos"], "1.9 3.2 8.6": ["quinellaed"], "5.2 2.2 5.5": ["amenties", "trian"], "5.2 13.3 7.8": ["ambulence"], "7.6 2.7 18.2": ["medicates"], "6.6 5.1 24.1": ["hebes"], "7.3 7.2 9.6": ["desorbed"], "25.2 22.8 12.4": ["autobot"], "15.8 7.3 3.3": ["buzzier"], "2.3 6.1 21.8": ["tei"], "-2.9 -0.4 -2.7": ["oad"], "1.3 12.3 9.6": ["grantsmanship"], "-0.0 7.6 8.1": ["wam"], "5.1 4.2 13.0": ["roz"], "3.5 43.3 3.8": ["counterterrorists"], "-2.3 21.2 19.5": ["barnyardgrass"], "10.2 7.4 0.6": ["talkability"], "1.4 19.1 5.0": ["interconfessional"], "-1.1 13.7 1.9": ["exhuberance"], "11.4 8.6 15.5": ["aahh"], "4.4 9.5 11.0": ["keller"], "-1.2 10.6 0.2": ["xxxxxxxxxx"], "0.3 13.7 2.1": ["pocketborough"], "12.0 7.8 17.9": ["rcb"], "-3.4 3.4 1.7": ["dantrolene"], "2.8 4.4 11.2": ["tackes"], "5.6 12.1 11.5": ["interpromotional"], "3.5 17.0 11.8": ["synchronism"], "2.4 -1.5 10.6": ["redosing"], "7.1 6.4 3.9": ["awhole"], "16.0 12.4 21.9": ["stinkweed"], "10.0 17.1 7.3": ["nonevents"], "5.3 10.6 10.5": ["giggs"], "1.0 10.4 -0.7": ["offiers"], "6.1 5.6 -0.8": ["namedrops"], "7.9 8.1 9.1": ["monocytogenes"], "-4.9 4.5 6.1": ["endoglin"], "-1.4 20.0 0.6": ["harrasing"], "13.9 -3.7 6.7": ["constrution"], "10.3 23.2 9.2": ["fieldcraft"], "3.8 6.9 30.4": ["arborio"], "-6.2 0.2 6.2": ["penological"], "11.2 -1.1 10.0": ["programas"], "0.3 19.4 9.5": ["fusionism"], "24.7 15.8 19.1": ["chieftan"], "19.3 10.3 34.7": ["smokie"], "10.0 4.0 -0.6": ["tosell"], "6.8 4.9 17.0": ["bhandara"], "8.4 12.7 6.9": ["uninterupted"], "12.6 6.7 1.1": ["moblie"], "-7.6 2.8 -5.2": ["supervison"], "9.6 1.6 1.7": ["delevered"], "0.1 18.8 2.3": ["combativity"], "7.6 6.1 14.0": ["doyle"], "6.1 19.8 5.4": ["hardto"], "-2.0 7.9 3.4": ["acto"], "14.6 11.6 2.6": ["browers"], "2.5 24.9 -0.4": ["abililty"], "4.6 5.3 10.3": ["outgrower"], "-3.4 4.9 9.7": ["stresser"], "17.3 6.4 1.0": ["sonification"], "-6.5 16.6 18.6": ["tablesetter"], "-3.2 0.8 0.5": ["coinvestigators"], "7.1 22.1 4.5": ["minatory"], "2.8 8.0 14.3": ["redisseminated"], "22.4 14.1 31.4": ["flecking"], "17.2 19.3 12.2": ["planchette"], "5.6 17.1 7.1": ["understeers"], "16.7 -0.1 37.7": ["porterhouses"], "-0.5 11.4 13.8": ["nikal"], "0.4 10.5 -2.8": ["photoblogs"], "8.2 0.9 15.4": ["prebudget"], "13.9 12.6 26.5": ["breezers"], "0.5 22.5 7.2": ["hardworker"], "12.4 6.4 16.7": ["arge"], "4.2 3.8 10.5": ["lafayette"], "14.5 -4.1 3.7": ["illycaffe"], "11.7 4.1 5.1": ["trol"], "21.5 10.8 35.0": ["whitecap"], "2.8 5.9 11.5": ["finns"], "10.4 18.6 12.1": ["veryone"], "18.6 15.6 24.5": ["yella"], "8.5 12.8 2.2": ["doublesix"], "11.6 20.9 10.8": ["kibbutzes"], "5.6 6.5 -1.3": ["betaken"], "0.6 2.5 -0.6": ["accpeted"], "6.1 11.7 11.4": ["basicaly"], "11.5 6.8 4.9": ["drinktec"], "8.2 2.4 26.2": ["citrussy"], "3.5 22.8 7.3": ["complicities"], "7.2 11.6 14.0": ["elliott"], "22.5 1.8 7.0": ["premarkets"], "16.0 4.3 1.3": ["superbody"], "7.7 5.3 17.0": ["hilary"], "10.0 3.4 13.2": ["grossout"], "3.5 2.7 7.2": ["coastbound"], "4.7 0.9 3.1": ["aris"], "4.7 7.8 9.2": ["biosequestration"], "2.2 2.5 6.1": ["reser"], "-4.8 5.6 6.5": ["levelof"], "8.8 1.4 10.1": ["nonroad"], "2.3 11.5 8.6": ["onm"], "10.6 11.7 24.9": ["manzanitas"], "18.7 4.1 17.9": ["toeless"], "13.8 14.8 20.9": ["dromaeosaurs"], "7.6 -0.2 4.8": ["aution"], "20.5 -0.3 1.1": ["holdco"], "9.6 13.6 18.3": ["denis"], "-2.1 7.6 12.0": ["tumakbo"], "12.2 24.7 9.9": ["unchastened"], "4.9 8.9 16.7": ["booo"], "-0.2 -0.1 -2.8": ["performancesoft"], "-0.1 3.2 10.7": ["nonfasting"], "2.6 19.8 13.9": ["dharmic"], "-0.5 -4.2 3.6": ["decarboxylase"], "11.6 21.4 3.1": ["perfidies"], "9.6 11.8 8.1": ["anywho"], "2.0 12.6 8.4": ["fireboss"], "7.5 -2.3 5.4": ["presentor"], "10.3 3.2 4.8": ["bruit"], "-1.7 12.9 8.5": ["liegt"], "8.2 6.1 8.8": ["cuming"], "1.4 7.1 1.8": ["tbsource"], "11.7 14.5 12.5": ["soundclash"], "10.4 20.8 8.1": ["nonsocial"], "3.3 13.6 11.5": ["melvin"], "-5.6 -0.1 4.5": ["vaild"], "13.8 6.0 2.4": ["strated"], "-1.3 0.7 5.1": ["endourology"], "6.5 14.8 12.4": ["demethylase"], "3.2 7.3 8.2": ["econometricians"], "6.2 19.9 17.9": ["weepiness"], "19.2 12.5 24.4": ["opaline"], "5.6 11.6 18.6": ["fittin"], "6.7 11.9 7.0": ["crowdpleasing"], "2.9 7.5 8.9": ["thisseason"], "1.8 -0.3 6.6": ["representa"], "2.1 19.0 6.7": ["untowards"], "-2.3 13.3 8.3": ["vicitim"], "-2.1 4.0 4.1": ["affliation"], "11.1 4.2 12.0": ["nyckelharpa"], "15.0 8.1 15.7": ["progessing"], "3.8 15.7 12.2": ["bellamy"], "-8.0 9.8 5.0": ["aggrieve"], "4.8 9.5 1.7": ["handcraftsmanship"], "-4.8 6.7 11.0": ["deconcentration"], "8.5 4.7 11.4": ["epididymal"], "4.4 2.8 19.4": ["koutou"], "1.0 4.7 2.2": ["carrried"], "7.5 7.9 6.1": ["autoconfiguration"], "-4.6 1.1 1.3": ["pitocin"], "3.7 -9.3 7.9": ["triannual"], "16.3 10.4 12.4": ["ravey"], "2.8 7.5 0.2": ["microspectroscopy"], "11.2 12.7 13.2": ["knap"], "8.9 2.5 -6.4": ["undermarketed"], "14.0 9.1 18.2": ["unguent"], "-2.2 1.3 11.9": ["menadione"], "19.0 13.0 12.7": ["kerbstone"], "7.8 3.7 41.1": ["cultch"], "11.7 6.8 13.3": ["boff"], "16.5 3.1 4.2": ["trippled"], "5.2 18.9 13.4": ["unoffensive"], "9.7 11.6 29.4": ["combers"], "8.3 -0.0 5.6": ["bosberaad"], "11.4 -1.0 29.5": ["dac"], "2.5 -0.5 11.7": ["yno"], "-0.4 13.3 4.7": ["bek"], "3.0 23.6 3.1": ["treasons"], "2.0 31.9 5.0": ["airmobile"], "7.4 15.0 5.3": ["disentangles"], "2.6 2.0 3.0": ["weeknd"], "6.2 1.5 12.0": ["vibhuti"], "13.0 8.7 13.0": ["presque"], "5.5 19.4 11.4": ["paytable"], "-5.8 2.5 1.2": ["conver"], "4.6 6.1 16.4": ["anodising"], "5.0 16.3 -0.4": ["conern"], "-6.4 2.3 5.8": ["programatic"], "22.0 8.2 20.5": ["restacked"], "9.6 18.4 13.6": ["jsams"], "1.0 7.0 5.0": ["findin"], "15.9 14.7 15.9": ["monkeywrench"], "7.3 10.9 8.5": ["chaar"], "-2.2 8.0 4.4": ["carnapped"], "7.8 18.7 6.3": ["extremley"], "6.9 3.0 7.2": ["arthralgias"], "20.9 6.2 7.9": ["welching"], "4.3 0.7 14.8": ["piastres"], "12.0 12.2 29.9": ["pipits"], "5.5 8.2 13.0": ["homeyness"], "0.1 6.8 15.3": ["hirap"], "8.8 4.3 23.1": ["pois"], "10.9 16.3 7.5": ["zeniths"], "6.2 5.9 5.4": ["sporozoite"], "4.7 -4.4 8.1": ["monts"], "18.1 13.1 19.0": ["guilded"], "-5.8 5.8 2.8": ["compre"], "4.4 -1.5 16.2": ["cuh"], "2.3 14.9 20.0": ["demodex"], "-1.4 13.0 7.1": ["mch"], "-6.4 13.6 -4.5": ["peacebuilders"], "0.7 17.8 0.8": ["premis"], "-0.3 21.8 9.0": ["dukkha"], "11.8 11.4 23.2": ["lighterage"], "12.5 -0.1 1.3": ["caravaned"], "13.6 11.2 16.1": ["shonks"], "9.7 9.8 11.0": ["chromatics"], "10.1 18.3 3.6": ["dominancy"], "5.8 19.1 3.1": ["demobilizations"], "5.9 14.4 10.3": ["pureblood"], "15.1 9.1 12.2": ["chyawanprash"], "0.3 13.5 -1.8": ["thero"], "17.1 20.6 22.7": ["straggles"], "9.6 12.1 18.7": ["unridden"], "2.1 7.8 -6.5": ["festschrift"], "8.1 25.2 11.9": ["democraps"], "1.1 -5.3 15.4": ["warwick"], "2.9 13.5 2.7": ["comprehensions"], "10.5 7.6 23.3": ["opsins"], "7.3 7.5 16.8": ["decalcified"], "14.0 6.9 30.6": ["bolillo"], "13.6 9.6 19.3": ["heartwarmingly"], "17.8 13.7 15.8": ["blogoshpere"], "9.9 14.2 2.6": ["waterboys"], "14.8 19.6 5.4": ["phoneys"], "2.4 17.3 21.2": ["uninfested"], "13.7 17.9 12.2": ["chloroformed"], "4.9 8.8 10.4": ["periodicities"], "8.7 4.2 5.5": ["ibiza"], "13.7 9.1 11.3": ["readyto"], "-0.6 6.9 6.4": ["craniectomy"], "4.5 18.8 -0.9": ["refernce"], "-1.9 20.0 1.8": ["gradualists"], "0.8 -0.1 5.3": ["lars"], "12.9 15.3 10.4": ["olfactometer"], "1.7 -3.4 14.9": ["fahl"], "-3.6 11.3 3.7": ["davened"], "5.4 10.6 10.5": ["thougth"], "3.4 -5.2 8.3": ["throatier"], "2.5 12.9 20.4": ["baril"], "21.6 18.4 41.0": ["livebait"], "5.3 12.2 -5.4": ["reflowable"], "-3.5 3.0 4.4": ["peptidase"], "-5.5 7.4 5.9": ["metabolizers"], "17.0 0.1 2.3": ["tecnobrega"], "11.9 6.8 30.0": ["batata"], "18.2 30.4 15.3": ["viscously"], "-0.6 16.2 -1.7": ["pirs"], "15.6 15.8 16.0": ["reseals"], "-1.5 6.6 13.2": ["podoplanin"], "2.6 15.8 6.5": ["transmural"], "-1.6 4.2 5.0": ["playwrite"], "6.1 16.5 1.9": ["irresponsive"], "10.7 7.2 21.0": ["santana"], "2.3 7.7 17.0": ["ngunit"], "-2.5 -1.8 9.3": ["ukoll"], "4.9 6.5 9.0": ["datasource"], "6.5 9.9 12.0": ["jamgrass"], "-7.8 3.8 6.5": ["affiants"], "-4.6 3.4 15.7": ["kenduri"], "-4.6 -0.7 -4.5": ["traunch"], "2.7 10.5 10.7": ["remined"], "20.5 10.9 14.5": ["biffy"], "0.3 15.8 8.5": ["wakeups"], "12.7 22.7 12.7": ["desolating"], "9.4 -4.1 12.3": ["prestressed"], "19.9 12.4 17.5": ["moue"], "20.2 8.9 20.4": ["dunkin"], "7.4 1.2 11.7": ["nonalcohol"], "9.0 15.5 14.1": ["commensurable"], "11.4 4.8 8.1": ["lipsynching"], "10.3 8.8 13.6": ["tir"], "-0.4 9.8 7.2": ["documenters", "megohms"], "-11.4 0.1 2.5": ["lanning"], "-0.2 0.3 4.0": ["broadbasing"], "7.6 9.4 9.6": ["mitiglinide"], "7.8 8.4 10.1": ["mpgs"], "11.4 4.2 18.0": ["cookshop"], "4.4 18.8 5.3": ["enterpriser"], "13.2 -2.9 2.1": ["cofinanced"], "-4.3 13.5 8.8": ["olam"], "13.1 2.6 7.6": ["bomp"], "4.1 18.3 8.5": ["bemedaled"], "11.3 14.9 9.0": ["baronies"], "5.7 10.9 25.2": ["lightships"], "9.5 14.0 15.1": ["contrada"], "26.3 18.2 14.9": ["anthropomorphised"], "1.0 14.3 -1.7": ["philsophy"], "3.4 -4.9 6.4": ["resurfacings"], "12.5 3.9 8.5": ["highgrade"], "12.9 12.9 35.9": ["choughs"], "9.3 2.9 16.5": ["sise"], "6.3 5.9 16.3": ["nuchal"], "10.6 4.8 -0.0": ["homecountry"], "17.4 14.5 6.1": ["suceeds"], "11.8 -4.4 16.5": ["ligh"], "-10.2 4.1 8.5": ["ostomates"], "-0.6 10.0 10.4": ["echolalia"], "14.6 17.8 13.8": ["punsters"], "18.3 22.2 5.3": ["giantism"], "-1.4 9.8 9.5": ["shochet"], "16.7 21.5 30.6": ["dogmeat"], "19.0 6.1 17.6": ["jerseyed"], "10.0 4.9 18.3": ["fibered"], "-1.0 13.6 10.3": ["pictorialist"], "-3.1 5.6 5.7": ["maturational"], "13.5 3.9 11.0": ["toch"], "12.9 9.0 13.3": ["cigarrette"], "12.2 17.8 14.3": ["neonicotinoid"], "16.4 6.1 25.1": ["iceboat"], "2.9 9.4 13.9": ["nonpermitted"], "8.9 8.9 4.1": ["dehumidified"], "2.9 19.4 10.4": ["opportunty"], "3.4 -1.9 5.5": ["nationaux"], "17.0 16.7 19.0": ["mimivirus"], "6.4 13.4 6.3": ["superantigens"], "12.6 1.1 17.0": ["argyles"], "5.4 13.8 0.5": ["hakeem"], "11.2 18.2 19.1": ["sybarites"], "10.1 13.7 -0.6": ["supportfor"], "-1.2 16.6 3.0": ["ecclesiastically"], "11.4 2.5 9.5": ["nanodot"], "0.7 10.0 14.8": ["hobe"], "5.8 23.2 30.8": ["breaklines"], "10.0 12.4 6.7": ["polariton"], "-2.7 5.7 -1.5": ["defated"], "-1.6 4.4 17.3": ["clayton"], "5.2 14.3 16.2": ["kovil"], "20.2 1.7 18.7": ["farthings"], "11.3 2.9 1.4": ["introducting"], "7.1 11.7 8.6": ["twitt"], "2.6 14.2 2.4": ["enounter"], "15.2 15.8 4.2": ["governemt"], "-2.7 2.9 3.0": ["hereupon"], "-5.4 5.9 -7.4": ["khatib"], "-2.4 14.6 -0.0": ["irritative"], "13.8 6.4 12.5": ["significan"], "0.4 2.1 5.8": ["oints"], "2.3 9.4 7.8": ["generalisable"], "13.1 4.2 12.4": ["maximiser"], "15.1 9.4 8.7": ["bizzarre"], "16.8 12.1 7.1": ["newsdesks"], "19.8 9.5 11.9": ["spaceward"], "9.7 38.5 13.5": ["gadhafi"], "8.2 8.2 -0.3": ["etwa"], "10.7 15.8 22.1": ["piemaker"], "11.2 15.1 2.6": ["codependents"], "3.0 20.5 5.4": ["surpressed"], "1.3 10.8 17.4": ["wonkishness"], "-2.9 -7.9 -4.7": ["pricipal"], "13.9 11.2 2.1": ["techcrunch"], "17.5 4.3 12.0": ["buildng"], "7.5 0.9 3.1": ["styrenic"], "1.2 -0.4 -1.6": ["imporved"], "3.8 0.3 9.8": ["dtv"], "9.4 7.4 8.8": ["airboarding"], "4.0 12.5 6.3": ["photoionization"], "17.4 14.7 2.9": ["attagirl"], "13.2 -2.1 12.0": ["ferme"], "35.0 29.7 31.7": ["goombas"], "12.1 12.3 10.6": ["jollied"], "8.4 2.2 8.4": ["proprio"], "6.8 24.6 3.9": ["vandalistic"], "-5.3 6.2 12.7": ["intrafamily"], "8.1 5.0 6.5": ["fficials"], "14.7 11.7 14.1": ["acquisitional"], "2.3 24.4 9.3": ["outfielded"], "10.0 17.0 12.5": ["damon"], "2.7 17.7 6.8": ["whowere"], "9.3 -3.9 0.4": ["choisi"], "5.6 4.4 9.6": ["involverisks"], "7.7 2.2 14.3": ["auckland"], "3.8 4.7 9.2": ["eather"], "3.6 18.3 3.9": ["efficently"], "2.0 5.3 4.0": ["nonadversarial"], "-0.7 -5.9 7.9": ["barg"], "6.9 5.8 1.4": ["reconceptualized"], "-1.6 12.8 6.6": ["preboarding"], "-0.0 5.6 1.2": ["teletypewriter"], "3.3 4.2 11.3": ["pinhooker"], "15.8 11.6 -2.1": ["biolabs"], "2.3 11.2 8.8": ["pouvoir"], "12.6 11.4 32.9": ["turtledove"], "13.6 2.1 15.4": ["phaeton"], "3.8 6.7 -1.3": ["andsupport"], "-12.1 0.8 -3.2": ["subscore"], "21.0 6.0 17.0": ["matts"], "14.0 6.7 0.9": ["uthorities"], "12.2 8.7 10.8": ["airbridges"], "22.2 8.0 23.2": ["choclate"], "4.9 7.3 9.9": ["talar"], "10.2 19.0 21.0": ["ectoparasites"], "5.5 -0.2 10.6": ["billables"], "11.5 6.4 4.6": ["romania"], "-0.2 2.7 1.4": ["awating"], "10.8 2.1 26.4": ["puer"], "10.7 10.8 3.1": ["cinematograph"], "5.4 10.7 21.8": ["snowclearing"], "-1.7 19.6 2.3": ["biassed"], "0.1 11.8 8.7": ["proadministration"], "17.3 4.7 14.8": ["heavweight"], "9.7 13.4 19.3": ["faber"], "8.6 5.2 17.6": ["muguet"], "-2.3 9.9 0.1": ["adoped"], "15.7 8.2 32.1": ["feluccas"], "11.1 7.4 2.5": ["vario"], "16.0 10.3 16.2": ["ophiles"], "12.4 7.8 13.4": ["genuinly"], "13.8 22.3 16.0": ["shooty"], "14.3 25.8 0.9": ["gungho"], "5.3 4.9 15.0": ["voiture"], "19.0 7.9 21.8": ["shadecloth"], "16.5 7.4 8.9": ["overspilling"], "-0.8 20.8 3.9": ["chareidim"], "0.2 5.4 10.0": ["thundercar"], "6.0 -7.1 5.5": ["esterday"], "-1.8 8.7 13.3": ["pantun"], "12.2 2.4 9.8": ["sportscoat"], "19.8 6.1 18.4": ["polychromed"], "6.3 7.0 3.7": ["unpromoted"], "5.4 17.4 11.0": ["visuality"], "12.7 15.2 6.5": ["unpoetic"], "12.8 0.6 17.4": ["crokinole"], "3.9 4.9 8.9": ["hyperemesis"], "8.0 8.6 6.6": ["tranching"], "1.9 1.0 0.3": ["darifenacin"], "3.3 8.7 5.3": ["witterings"], "5.6 7.8 12.9": ["firstbase"], "10.0 12.3 27.7": ["overstory"], "4.5 -0.6 7.6": ["rown"], "17.9 12.1 15.3": ["swirlies"], "10.4 18.4 -3.2": ["placeman"], "11.5 9.2 23.9": ["cocotte"], "2.4 18.6 1.7": ["unwaivering"], "2.1 11.6 12.6": ["acha"], "10.8 7.1 14.7": ["rainscreen"], "8.6 12.2 7.4": ["redivided"], "-0.5 6.8 8.4": ["disabilties"], "1.3 17.4 2.7": ["amal"], "10.4 8.2 23.3": ["daps"], "-10.0 7.1 6.0": ["crimeline"], "8.5 7.0 12.9": ["slitted"], "0.8 6.3 11.8": ["arteriosclerotic"], "0.3 9.1 6.3": ["balak"], "14.7 0.8 12.3": ["canalisation"], "4.4 3.4 14.6": ["tkun"], "15.3 22.4 12.1": ["assymetric"], "-7.5 12.8 6.9": ["germaine"], "2.1 18.1 2.5": ["comandantes"], "-2.4 2.5 12.0": ["jackscrews"], "-1.1 2.9 8.8": ["coor"], "9.0 21.2 4.6": ["stalag"], "6.4 1.7 18.7": ["dayon"], "-0.4 4.3 4.9": ["lidlifters"], "20.8 14.8 16.3": ["cutsey"], "9.1 8.0 24.4": ["facecloth"], "3.3 10.9 10.4": ["methylxanthine"], "7.2 16.2 8.3": ["disproportionably"], "-1.1 -0.1 1.9": ["interchurch"], "17.0 9.8 6.5": ["smashups"], "1.8 5.0 20.5": ["holliday"], "8.0 9.9 17.1": ["overpainted"], "9.6 4.1 17.1": ["ortholog"], "2.4 -5.1 9.6": ["corso"], "13.7 -2.3 5.1": ["memorablia"], "-5.1 2.5 6.0": ["unentitled"], "2.0 7.2 8.9": ["nares"], "5.1 15.8 28.2": ["woodrat"], "-4.5 15.3 4.2": ["catechized"], "31.0 16.4 27.5": ["chomper"], "6.6 -11.5 13.8": ["fourmonth"], "6.1 9.3 14.1": ["comfit"], "2.8 11.0 22.9": ["tastants"], "11.7 -2.8 3.3": ["redleaf"], "3.8 11.9 34.6": ["yellowlegs"], "10.8 12.9 4.7": ["workcells"], "12.5 14.9 13.5": ["carborundum"], "6.2 6.7 16.1": ["pestis"], "18.0 4.8 15.3": ["slackest"], "10.3 6.4 11.4": ["pomades"], "0.7 14.4 7.3": ["uninterpretable"], "21.4 26.0 19.7": ["concuss"], "8.8 14.3 8.9": ["autoloading"], "10.5 16.2 15.9": ["hitcher"], "3.5 7.0 2.0": ["resonsible"], "10.4 1.3 18.7": ["salchows"], "18.3 10.3 11.2": ["richies"], "2.4 6.2 16.7": ["binger"], "-2.1 -1.7 -0.9": ["extravascular"], "15.2 13.2 9.2": ["arachnoid"], "11.2 10.2 3.5": ["taxdollars"], "7.2 11.1 8.4": ["complainin"], "1.2 11.8 5.0": ["unmute"], "12.8 7.3 6.4": ["adserving"], "7.0 3.3 16.2": ["crushings"], "9.1 42.0 7.6": ["panzers"], "2.8 3.7 9.9": ["biogs"], "-4.2 9.6 -0.6": ["programmess"], "14.8 14.1 8.7": ["socializers"], "-0.3 13.7 3.4": ["offficer"], "12.0 16.4 13.7": ["foxnews"], "9.2 10.5 14.7": ["pintle"], "9.2 2.3 3.6": ["foulup"], "2.2 19.8 0.3": ["politicises"], "-1.7 7.6 10.8": ["enterotoxin"], "0.5 4.1 14.8": ["sigurado"], "2.3 5.7 17.4": ["ballard"], "2.0 3.2 28.8": ["goreng"], "5.6 11.9 0.4": ["unmodernised"], "13.4 18.3 9.0": ["closable"], "1.5 0.3 5.0": ["dimissal"], "6.2 9.4 1.6": ["metalloproteinase"], "-12.5 17.7 2.9": ["signators"], "13.3 17.7 9.4": ["sleazily"], "0.5 21.5 15.1": ["bipartisanly"], "10.8 20.3 13.5": ["hesays"], "12.0 9.2 13.6": ["hugfest"], "-2.9 4.4 9.0": ["shradh"], "3.3 4.4 12.4": ["salseros"], "10.5 13.8 4.6": ["dabke"], "14.3 20.4 8.3": ["illuminant"], "-2.8 9.0 -3.7": ["breathalysing"], "6.2 12.5 12.2": ["subgenus"], "9.7 3.5 8.2": ["threaders"], "8.8 -3.5 1.7": ["derivatized"], "9.5 9.5 11.3": ["ignimbrite"], "-0.9 1.7 3.3": ["wwith"], "2.5 16.7 8.6": ["ruach"], "28.9 21.4 32.6": ["mantises"], "2.4 27.3 2.0": ["libration"], "12.9 8.6 9.0": ["alling"], "-1.0 1.5 16.1": ["methode"], "-10.3 9.7 9.2": ["multimember"], "24.1 17.8 12.2": ["wheatfield"], "14.4 -0.1 4.6": ["multifuel"], "6.3 4.1 11.5": ["benadryl"], "2.8 9.4 12.7": ["salamat"], "10.1 5.0 1.7": ["mobilephones"], "11.7 0.9 9.6": ["milliarcseconds"], "-3.6 -2.3 -0.6": ["graudate"], "10.0 13.4 -4.3": ["broadcastings"], "6.4 -1.0 2.5": ["xvid"], "18.5 6.6 11.9": ["rumpling"], "-2.5 8.4 -7.8": ["nothave"], "3.7 8.8 16.2": ["windmiller"], "0.2 0.4 1.5": ["nonsalaried"], "13.4 -5.1 2.0": ["diecasts"], "11.0 7.0 20.6": ["underskirts"], "1.8 24.9 -1.6": ["havocs"], "6.5 37.3 2.0": ["grouplet"], "6.5 -1.4 1.2": ["specia"], "7.0 21.8 11.8": ["poitical"], "-5.3 0.2 14.6": ["silages"], "17.3 4.9 21.4": ["cornucopian"], "20.7 18.7 30.7": ["wabbits"], "14.6 3.3 20.1": ["geomancer"], "11.9 6.8 11.9": ["volution"], "15.5 3.7 19.5": ["microdroplets"], "-5.6 1.6 4.9": ["sammelans"], "10.8 0.7 6.9": ["pushdown"], "-6.5 1.1 0.9": ["dysrhythmia"], "8.0 18.0 3.3": ["rosily"], "-1.1 25.9 10.0": ["nagger"], "0.3 13.8 0.5": ["emergeny"], "6.3 0.1 -0.3": ["cenderitide"], "0.7 3.8 5.6": ["dextropropoxyphene"], "5.6 15.9 8.6": ["externalizes"], "-6.4 21.2 5.9": ["estranges"], "20.6 17.9 19.4": ["limbing"], "16.6 -10.1 0.8": ["signmaking"], "0.6 9.5 -0.5": ["phonation"], "19.5 0.0 3.7": ["stockboy"], "3.8 -0.8 1.9": ["upfits"], "12.0 4.3 4.2": ["bloggable"], "-1.7 8.9 5.7": ["imi"], "4.5 2.3 8.2": ["moduli"], "13.0 16.5 19.0": ["guida"], "9.6 -1.4 7.0": ["zie"], "1.6 11.5 7.6": ["ratifiable"], "3.5 1.5 7.2": ["supplychain"], "-1.4 4.6 16.1": ["kaysa"], "24.2 13.3 11.6": ["pillager"], "1.1 18.3 1.5": ["muqata"], "5.4 -2.3 14.7": ["mlynedd"], "3.2 6.6 9.3": ["choatet"], "7.6 12.5 5.8": ["thruways"], "11.0 10.5 14.3": ["dirrty"], "6.1 14.4 1.9": ["nonsignatory"], "3.5 21.5 11.6": ["nonconscious"], "13.4 -12.9 4.7": ["withmore"], "9.2 -2.9 12.2": ["linea"], "7.2 8.4 -2.9": ["splashproof"], "7.8 1.4 9.2": ["polyisoprene"], "4.0 15.8 17.3": ["resends"], "10.3 11.2 16.4": ["selvedge"], "-9.0 11.6 1.6": ["chehlum"], "5.2 6.1 10.3": ["paraesthesia"], "7.5 6.5 10.7": ["entrancingly"], "-0.1 25.0 11.8": ["malinger"], "11.8 5.8 2.7": ["microblogger"], "5.8 20.6 2.6": ["ultraright"], "16.3 0.5 22.2": ["gato"], "0.9 -5.3 -8.1": ["headof"], "9.4 17.5 9.9": ["begorrah"], "6.2 5.3 10.4": ["jounce"], "15.7 -3.7 12.7": ["sexo"], "25.4 21.1 35.0": ["lanternfish"], "11.1 4.7 6.1": ["brassed"], "6.6 0.5 4.2": ["joueurs"], "0.8 -5.9 -5.4": ["reguarding"], "1.6 2.0 4.5": ["ealth"], "4.7 9.1 12.4": ["humko"], "11.2 16.0 9.9": ["oomycete"], "-0.7 -4.0 -2.3": ["benfluorex"], "-6.1 16.0 1.6": ["antecedence"], "10.4 8.5 6.6": ["doggish"], "4.0 9.9 13.1": ["cynthia"], "4.6 3.1 9.7": ["adolescences"], "12.5 9.2 24.5": ["nemesia"], "9.4 2.9 11.7": ["underseat"], "-6.8 1.9 4.7": ["emendations"], "6.7 9.1 24.9": ["turbidites"], "6.6 22.6 13.7": ["aslong"], "11.1 -3.6 7.7": ["tetrahydrofuran"], "6.0 1.7 19.2": ["nien"], "19.8 2.2 -3.5": ["magink"], "3.7 6.9 11.3": ["informes"], "15.1 7.3 5.7": ["experiements"], "0.7 10.1 9.9": ["dexpramipexole"], "14.2 21.0 5.6": ["prashant"], "6.5 5.3 25.3": ["chokeberries"], "10.7 11.5 19.0": ["forumla"], "7.1 9.2 27.7": ["presoak"], "9.1 16.3 5.2": ["stabilty"], "-0.9 8.4 2.8": ["nattuvangam"], "3.7 6.3 14.2": ["baritonal"], "-3.3 9.8 -3.2": ["trokosi"], "-1.2 -0.1 3.7": ["candidat"], "4.7 5.6 12.6": ["poppish"], "8.8 4.0 3.8": ["andor"], "27.4 -6.3 2.8": ["wallscape"], "4.1 4.3 4.3": ["libtiff"], "6.0 -1.8 4.9": ["transportaion"], "20.0 10.8 28.8": ["brugmansia"], "15.4 11.2 9.6": ["steambath"], "6.1 2.7 -5.8": ["higlights"], "11.9 5.2 22.0": ["blackeye"], "0.9 10.7 9.5": ["sphingolipid"], "14.3 -2.1 9.6": ["bitesize"], "6.7 9.9 8.5": ["offce"], "-3.4 5.1 14.5": ["tshogpa"], "15.0 2.6 0.7": ["startlet"], "13.7 13.6 6.1": ["squalour"], "11.1 15.0 22.9": ["tristeza"], "-1.9 18.1 -0.6": ["openmindedness"], "11.6 9.5 13.4": ["snobbiest"], "13.5 7.7 4.8": ["telvision"], "4.2 6.7 9.0": ["instantiates"], "9.5 5.4 15.4": ["onde"], "3.5 7.3 4.4": ["webhead"], "2.2 9.4 4.0": ["interoperated"], "-2.4 7.0 3.1": ["upskilled"], "4.9 7.7 12.5": ["durant"], "4.0 12.4 15.3": ["doodh"], "5.8 11.4 -1.8": ["nited"], "14.5 5.1 1.8": ["munich"], "7.4 7.2 10.7": ["citoyens"], "21.5 8.1 10.2": ["desposits"], "-2.6 12.2 4.0": ["snowouts"], "8.6 7.0 8.8": ["rochester"], "18.7 16.0 21.0": ["henges"], "10.0 11.0 4.3": ["univers"], "3.9 9.2 7.8": ["ngls"], "13.9 12.7 21.4": ["stubbier"], "-3.6 17.7 12.0": ["avoidances"], "9.2 11.4 -0.2": ["hre"], "12.9 29.5 8.1": ["fortressed"], "9.6 17.1 35.1": ["breakline"], "-5.8 2.3 -9.3": ["manufacturingtalk"], "0.7 6.0 10.5": ["trinidad"], "14.7 8.0 21.2": ["seabottom"], "4.9 14.5 8.0": ["libby"], "-3.6 -2.5 8.1": ["kbit"], "-0.8 0.7 3.5": ["chacun"], "-0.1 8.1 15.5": ["pagkakataon"], "22.2 11.9 14.3": ["craplets"], "7.5 17.0 9.2": ["magnetrons"], "7.9 11.2 13.4": ["nakshatra"], "13.9 -2.4 10.8": ["puchases"], "22.8 -0.9 13.2": ["lorryload"], "11.0 13.5 9.1": ["tailspinning"], "11.1 29.2 14.2": ["boomstick"], "21.1 18.9 20.8": ["thunks"], "2.4 19.7 19.6": ["reinfestation"], "8.1 12.6 8.5": ["undersizing"], "15.9 18.0 18.1": ["razorbacks"], "4.4 30.1 10.5": ["unpeaceful"], "6.6 2.1 9.4": ["layerings"], "7.7 4.5 12.1": ["litheness"], "-6.3 4.0 13.8": ["shortstaffed"], "5.5 18.7 8.1": ["unrelievedly"], "12.7 8.0 22.4": ["sasa"], "4.6 15.8 13.5": ["shounen"], "-11.5 -2.2 -2.9": ["neurocognition"], "20.9 14.3 14.3": ["ohmygod"], "2.4 3.7 4.5": ["heparins"], "10.1 3.8 17.2": ["meep"], "1.9 23.1 6.9": ["expertness"], "2.1 0.9 11.6": ["microlitres"], "11.1 11.7 -2.5": ["airmotives"], "-0.0 -6.3 9.2": ["bse"], "4.3 6.3 10.7": ["dirttrack"], "-0.6 -0.8 5.6": ["nondisplaced"], "3.4 -6.5 0.6": ["cty"], "-0.4 4.3 -3.3": ["aturday"], "0.5 14.7 12.3": ["kot"], "7.9 -0.3 35.1": ["bibb"], "4.7 8.3 3.8": ["disregulation"], "5.0 13.0 4.6": ["govrnment"], "-3.9 5.6 -7.3": ["fromtheir"], "10.3 9.7 18.3": ["hastings"], "0.3 17.2 18.4": ["bishonen"], "2.9 -0.6 5.1": ["andfor"], "6.3 11.5 13.9": ["schtupping"], "15.0 -3.3 14.7": ["pelletization"], "11.6 24.4 9.8": ["satanically"], "3.6 8.2 18.4": ["reticulata"], "9.0 6.7 18.5": ["asthetic"], "10.2 8.5 3.2": ["informatic"], "10.2 7.2 31.0": ["nephrite"], "13.4 17.7 14.3": ["espaliers"], "1.5 25.7 7.4": ["aryan"], "11.0 0.5 7.1": ["choirgirl"], "11.4 10.8 8.4": ["blazon"], "4.7 6.8 8.4": ["autorities"], "5.3 7.2 3.9": ["nexgen"], "17.7 11.1 1.7": ["deodorising"], "9.3 6.8 16.2": ["upfor"], "10.7 5.2 6.6": ["risktaking"], "10.2 20.9 6.4": ["mythologise"], "15.7 8.4 6.5": ["vaporiser"], "8.3 2.3 11.1": ["adjoint"], "10.2 4.6 25.2": ["bigas"], "8.3 10.0 8.6": ["knobhead"], "6.0 16.5 2.5": ["diakonia"], "-5.0 7.5 2.5": ["transconductance"], "8.9 17.4 14.6": ["postup"], "20.0 1.7 8.9": ["commecial"], "10.0 45.7 17.7": ["badguys"], "1.7 11.4 19.2": ["cyaan"], "-6.4 12.2 8.4": ["gaves"], "21.1 10.8 11.2": ["phut"], "4.6 10.5 13.7": ["negs"], "11.5 7.0 26.8": ["levain"], "0.9 7.5 11.7": ["rinkmates"], "7.3 5.0 15.6": ["jazzbo"], "9.1 18.6 10.6": ["theywould"], "-0.9 15.6 9.0": ["psychopathologies"], "16.7 23.8 15.7": ["subserviently"], "0.9 10.8 7.1": ["fundementals"], "17.9 10.5 29.6": ["bundt"], "4.8 8.0 6.8": ["tehn"], "-0.1 23.1 12.5": ["twere"], "10.0 7.4 16.1": ["sideliners"], "20.7 14.8 5.2": ["buggiest"], "-4.8 -4.8 0.3": ["enc"], "13.0 4.7 8.1": ["commercializable"], "0.4 22.6 6.3": ["serbs"], "14.5 6.7 22.1": ["fromages"], "5.9 9.1 18.7": ["sedimented"], "5.8 2.3 3.4": ["kpc"], "4.3 2.1 1.3": ["decertifies"], "14.5 17.5 10.2": ["powerslides"], "16.6 18.7 21.1": ["ringsteps"], "1.4 10.5 8.2": ["twoout"], "0.1 3.2 1.0": ["observership"], "6.4 -0.0 8.1": ["partita"], "0.9 3.6 12.6": ["skinfolds"], "20.2 12.4 19.9": ["cornfed"], "9.5 6.1 6.8": ["ironmaster"], "-5.2 15.6 2.9": ["emergently"], "-1.5 3.0 15.9": ["fiorentina"], "-2.9 6.3 1.9": ["pyschiatrist"], "9.1 16.4 9.3": ["azobenzene"], "2.6 7.3 6.7": ["sandro"], "0.1 1.2 0.1": ["unbureaucratic"], "-4.3 18.0 -2.7": ["insensitiveness"], "3.5 -2.9 -1.1": ["internationa"], "1.6 23.4 7.4": ["pointedness"], "30.2 -0.7 9.0": ["supermaket"], "2.5 8.5 2.9": ["artus"], "11.9 9.8 14.2": ["unitiated"], "3.0 5.5 10.9": ["karanga"], "-6.9 -0.0 4.8": ["ponits"], "6.7 6.8 13.7": ["intercropped"], "17.5 12.8 16.2": ["tailboard"], "-0.1 12.0 5.1": ["untolled"], "-4.0 -0.3 10.6": ["corre"], "13.1 -4.6 8.3": ["soapmaker"], "9.3 4.8 2.9": ["distinguised"], "13.5 4.9 8.1": ["bioproduct"], "5.5 15.9 15.0": ["oneliners"], "7.6 10.2 16.2": ["dutty"], "4.8 15.8 8.3": ["christain"], "7.8 -1.7 -3.8": ["runn"], "10.9 10.5 32.2": ["edulis"], "8.0 3.9 39.9": ["pesce"], "-5.1 15.0 13.7": ["familicide"], "3.8 8.2 -0.9": ["painfree"], "20.0 24.7 -3.8": ["goosestepping"], "9.4 17.7 11.5": ["upsettingly"], "12.0 5.3 7.0": ["dirtgirlworld"], "12.4 31.9 3.2": ["cyberterror"], "1.7 8.0 16.0": ["parsimoniously"], "1.3 1.8 3.7": ["tetravalent"], "6.3 -6.1 7.4": ["rulebreaking"], "3.2 19.1 4.9": ["dillusional"], "-1.1 3.1 18.2": ["floristic"], "14.6 5.5 17.0": ["jarveys"], "16.7 13.1 13.2": ["chorography"], "9.1 1.3 12.9": ["huis"], "-6.7 0.5 8.2": ["educe"], "5.5 8.2 11.1": ["decompilation"], "4.3 5.7 20.1": ["tiro"], "-3.8 5.1 3.7": ["reaccommodated"], "2.7 5.5 2.1": ["nondisclosures"], "-1.6 10.5 1.4": ["fateha"], "19.1 11.1 6.1": ["apublic"], "12.4 13.4 20.4": ["hamentashen"], "0.5 14.0 22.9": ["johnsongrass"], "10.2 27.4 18.0": ["disaggree"], "0.0 6.5 7.3": ["predictible"], "-0.7 2.3 1.7": ["dalteparin"], "9.5 10.9 6.9": ["hissyfit", "globalwarming"], "7.3 4.7 3.1": ["selfhelp"], "7.2 6.6 8.8": ["transfrontier"], "5.0 0.2 15.2": ["geos"], "4.8 21.7 1.9": ["corupt"], "6.1 9.6 5.4": ["glamourized"], "7.8 5.1 5.8": ["previsto"], "-9.9 17.0 12.8": ["pasuk"], "-8.2 0.4 10.4": ["neutropenic"], "8.5 3.3 18.8": ["highjinks", "leadframes"], "2.2 6.2 9.8": ["meaningof"], "6.5 13.8 21.0": ["ectomorph"], "11.8 18.1 3.6": ["duumvirate"], "7.8 34.7 12.0": ["katyusha"], "7.3 -1.2 20.0": ["lele"], "7.9 2.5 -1.4": ["inaddition"], "6.0 4.7 15.5": ["windsurfed"], "7.2 10.4 7.9": ["meganuclease"], "3.2 5.5 36.3": ["mataitai"], "-13.8 0.3 10.2": ["rotarian"], "20.9 16.0 23.1": ["ankylosaur"], "13.3 2.3 8.6": ["milimeters"], "-2.2 7.6 3.7": ["cheder"], "17.8 12.8 26.3": ["bougainvillaea"], "19.9 9.6 6.7": ["intrapreneur"], "0.7 8.8 9.7": ["headcovering"], "17.2 14.7 10.0": ["airglow"], "0.2 8.5 14.2": ["gelation"], "-3.0 3.3 8.9": ["aal"], "9.7 9.4 13.7": ["balla"], "2.6 5.8 5.2": ["andover"], "5.8 -1.8 21.0": ["paladar"], "5.0 16.5 16.9": ["protocell"], "2.6 17.8 2.2": ["excoriations"], "9.1 1.5 3.3": ["pfj"], "19.5 12.8 33.7": ["recurved"], "6.9 2.2 2.8": ["mcu"], "14.6 6.5 23.9": ["piloncillo"], "6.9 5.9 6.9": ["faceguards"], "9.1 14.9 5.6": ["obituarists"], "19.6 7.2 19.4": ["hardbodies"], "4.6 -7.5 -3.6": ["tml"], "10.9 2.6 15.9": ["phacelia"], "2.0 2.3 -0.2": ["amountof"], "0.1 17.6 0.2": ["cetainly"], "16.0 8.3 25.1": ["doop"], "5.2 8.7 4.3": ["retur"], "15.3 6.5 34.3": ["peanutty"], "-0.4 9.7 22.5": ["malama"], "9.7 5.9 29.3": ["caerulea"], "18.0 14.0 40.0": ["boletes"], "7.1 5.9 8.5": ["myoglobinuria"], "20.6 0.5 5.5": ["rejiggers"], "10.4 32.7 6.9": ["dissimulate"], "8.6 11.5 14.5": ["muzzy"], "-5.4 8.9 11.4": ["countian"], "10.5 15.4 7.0": ["gamerpoints"], "-1.9 0.7 2.4": ["heptathalon"], "0.2 12.7 1.7": ["uncommented"], "-0.3 13.0 9.3": ["gaybashing"], "3.5 5.5 12.8": ["coverable"], "3.5 1.7 4.5": ["mepolizumab"], "4.7 5.9 17.6": ["ciliated"], "3.8 0.6 15.2": ["impor"], "-7.1 9.9 2.8": ["warrented"], "2.3 7.7 17.7": ["heliski"], "-8.7 8.1 2.3": ["ody"], "12.8 3.9 53.0": ["caplin"], "7.5 8.3 0.8": ["biosimulation"], "4.9 5.5 19.9": ["tenga"], "9.8 -0.3 -0.7": ["innotek"], "14.1 4.2 9.0": ["losss"], "6.2 0.6 15.3": ["bahts"], "4.4 9.0 10.0": ["foreland"], "7.9 14.7 21.9": ["diphthong"], "-6.6 15.5 5.1": ["uninstructed"], "-7.2 2.8 8.6": ["atts"], "14.9 8.4 7.8": ["tailcone"], "9.5 1.1 10.6": ["mcgee"], "5.2 12.0 8.4": ["microcirculatory"], "2.9 4.6 6.9": ["diamine"], "0.8 9.7 9.8": ["anthropologic"], "0.4 0.7 7.6": ["unil"], "5.4 23.4 8.2": ["satphones"], "18.9 9.8 23.8": ["cordovan"], "7.4 -2.7 18.0": ["skillathon"], "21.9 11.6 23.7": ["wolfhounds"], "0.6 17.5 7.4": ["incoherency"], "10.3 11.1 6.8": ["sadomasochists"], "21.5 10.9 5.1": ["spokesanimals"], "9.4 11.2 9.8": ["teeshirt"], "8.6 12.4 14.0": ["steeve"], "4.5 3.7 -0.2": ["tomanage"], "4.3 -0.9 14.1": ["textless"], "13.6 5.8 34.9": ["tulles"], "-1.8 -5.7 6.4": ["dss"], "-2.1 14.1 8.6": ["extensors"], "5.8 6.5 6.3": ["femal"], "15.8 11.5 6.2": ["sureshot"], "0.4 5.8 11.7": ["labas"], "3.8 1.3 9.7": ["prend"], "18.0 0.7 11.1": ["bodypaint"], "3.8 -2.6 12.3": ["labwork"], "-2.2 5.6 6.7": ["eleciton"], "4.9 6.6 4.0": ["campagn"], "12.6 8.8 14.6": ["diecutting"], "2.4 11.6 12.9": ["barrett"], "12.5 1.3 14.7": ["lakehouse"], "-14.6 6.8 -8.0": ["vestigation"], "-2.8 11.3 11.5": ["thanatology"], "1.6 7.1 10.6": ["nek"], "-2.3 1.6 5.4": ["presurgery"], "5.2 5.7 9.7": ["maks"], "17.8 -0.7 2.6": ["cityowned"], "8.6 8.6 2.7": ["renault"], "10.3 22.4 10.5": ["antiscience"], "2.0 -0.9 25.3": ["kailan"], "12.6 19.2 5.6": ["electrosensitivity"], "6.3 17.1 0.4": ["suppporters"], "7.1 11.0 14.8": ["pasodoble"], "5.9 7.8 8.7": ["oppportunities"], "-10.5 9.4 3.2": ["formators"], "5.9 2.3 13.4": ["uncon"], "-4.2 21.3 10.7": ["catastrophize"], "9.4 4.7 6.9": ["substanial"], "6.1 2.2 2.8": ["seule"], "8.0 -4.7 10.4": ["altri"], "23.6 -0.9 8.1": ["signmaker"], "14.3 13.9 10.2": ["unclipping"], "3.3 13.6 10.3": ["iller"], "4.0 14.3 5.1": ["snubbers"], "14.8 6.5 10.0": ["technolog"], "19.5 9.7 19.4": ["teeterboard"], "12.8 1.2 9.1": ["almanack"], "-3.4 9.6 13.8": ["sapna"], "6.7 1.8 6.9": ["nonmanagerial"], "1.0 -0.4 9.6": ["healthplex"], "23.2 3.5 32.0": ["sealion"], "3.2 10.3 9.4": ["inegalitarian"], "-6.3 -5.6 8.8": ["sixweek"], "11.9 8.7 12.5": ["caffine"], "17.4 3.7 -0.7": ["aeroengine"], "3.0 31.6 5.9": ["followees"], "-3.9 10.9 5.4": ["myectomy"], "-8.1 3.3 12.4": ["assemblywomen"], "13.0 -1.4 4.2": ["marca"], "2.0 7.5 9.2": ["pyrochlore"], "1.2 10.8 11.2": ["atractive"], "17.3 14.6 17.1": ["hybridise"], "14.5 14.3 6.1": ["catchily"], "8.5 -0.8 9.1": ["quale"], "10.3 18.6 7.7": ["stultification"], "27.8 12.2 26.6": ["wetly"], "1.4 3.8 9.7": ["copyeditors"], "-0.3 9.5 10.1": ["elderlies"], "-4.4 15.2 5.0": ["antitrafficking"], "-2.4 2.9 12.7": ["moisturisation"], "-0.7 8.7 9.4": ["coracoid"], "7.3 -1.6 12.1": ["deel"], "10.5 15.3 9.8": ["europhiles"], "14.8 12.6 9.6": ["tapdancing"], "16.8 18.7 13.4": ["scintillated"], "1.9 24.0 6.5": ["barak"], "4.9 10.6 8.7": ["mandy"], "10.1 23.2 -2.1": ["difficut"], "17.3 0.1 3.3": ["nanometrology"], "21.8 7.5 21.0": ["ponces"], "2.9 14.7 5.6": ["priyanka"], "7.1 11.7 1.3": ["titel"], "2.3 5.0 15.5": ["snan"], "4.6 7.3 5.4": ["nonvoter"], "-7.5 5.1 7.0": ["indivual"], "8.7 7.4 15.5": ["doma"], "1.0 9.3 13.4": ["embarkment"], "3.0 -4.2 -0.5": ["coverge"], "14.6 -2.6 14.7": ["infusers"], "5.2 1.0 23.8": ["naay"], "1.8 32.0 -0.6": ["obscurants"], "-8.1 -0.1 6.6": ["nongraduates"], "2.9 11.1 9.6": ["lacrimal"], "12.2 5.6 0.5": ["inone"], "-1.2 1.9 11.4": ["jrh"], "2.2 -6.0 -2.4": ["tributed"], "7.1 18.1 8.0": ["ungrammatically"], "13.4 6.6 18.4": ["holdem"], "5.2 5.6 14.3": ["perfecta"], "7.6 5.5 10.1": ["aaaa"], "21.0 4.1 17.7": ["peavey"], "-5.1 3.8 -5.5": ["pointguard"], "-0.9 10.1 8.9": ["trave"], "3.3 10.3 9.5": ["heterodyne"], "18.3 0.4 16.3": ["tablemats"], "11.6 15.7 5.1": ["peoplein"], "4.3 4.8 8.2": ["stri"], "11.8 27.6 10.1": ["kikes"], "1.6 0.1 11.5": ["predix"], "10.4 24.7 18.5": ["corpuscle"], "7.3 9.1 22.1": ["naringin"], "4.8 26.8 3.5": ["discursively"], "11.5 5.0 4.9": ["teetotalling"], "2.7 22.5 2.6": ["noway"], "10.1 6.4 7.5": ["geomagnetism"], "13.0 12.8 21.2": ["unsweet"], "2.4 22.5 12.0": ["wingwoman"], "-2.4 6.1 6.9": ["thymosin"], "16.3 28.5 19.0": ["fumblers"], "4.7 9.8 -7.8": ["outqualifying"], "18.8 7.9 11.7": ["clsoe"], "22.1 8.8 16.9": ["upchucked"], "12.5 11.7 17.2": ["nougats"], "2.8 8.3 0.2": ["minut"], "8.7 19.8 11.3": ["yeomanry"], "3.9 1.9 19.7": ["iw"], "21.8 12.7 10.8": ["watersplash"], "-1.8 1.0 7.3": ["penner"], "13.2 19.8 12.0": ["moonsaults"], "14.1 20.7 4.4": ["baldfaced"], "5.9 16.6 5.8": ["bastmen"], "9.0 5.3 12.1": ["foc"], "3.1 8.0 6.4": ["nonfinal"], "13.4 19.1 6.4": ["misnaming"], "14.6 24.2 11.4": ["viperous"], "1.9 -0.4 8.8": ["ples"], "16.7 -4.5 6.7": ["suitmaker"], "11.7 8.1 28.6": ["barky"], "7.2 9.5 15.4": ["gwine"], "8.1 18.3 7.0": ["churnalism"], "-0.2 15.5 2.2": ["conciliations"], "11.1 2.5 10.9": ["iesy"], "1.5 12.4 13.3": ["codynews"], "-0.7 10.0 26.2": ["kurma"], "12.5 1.6 -0.1": ["prgramme"], "-1.1 7.0 16.5": ["magawa"], "7.4 1.2 19.8": ["torc"], "9.1 15.9 7.8": ["chummier"], "16.3 14.1 1.7": ["defibrillating"], "13.5 7.7 21.7": ["eddied"], "13.4 7.7 -2.5": ["akey"], "12.5 25.6 -4.5": ["aeriel"], "-0.9 3.9 9.6": ["allopregnanolone"], "1.3 -3.6 -5.6": ["inmore"], "8.3 13.9 10.6": ["exboyfriend"], "-3.6 4.8 1.6": ["replys"], "9.5 8.4 42.5": ["fishballs"], "8.6 4.7 30.2": ["godwit"], "4.8 2.3 2.0": ["rable"], "13.8 13.9 18.0": ["heelside"], "-7.3 13.7 4.2": ["teratogens"], "-5.0 14.2 11.4": ["radiosensitive"], "2.8 20.6 5.0": ["machomen"], "-0.2 0.4 -0.1": ["aplication"], "-2.5 10.5 13.2": ["caan"], "4.7 5.6 14.7": ["superfun"], "19.3 45.2 11.5": ["supersoldiers"], "-1.5 -3.7 3.7": ["endografts"], "-0.5 7.4 16.7": ["galit"], "17.0 28.0 17.5": ["mechas"], "9.2 11.6 9.0": ["semitone"], "9.9 7.8 13.8": ["blockier"], "-0.1 13.6 2.2": ["reproves"], "22.2 14.2 19.9": ["blimmin"], "-1.1 -0.2 0.8": ["keto"], "-1.5 14.9 10.9": ["aayega"], "7.0 -1.1 8.3": ["anigh"], "-1.2 12.8 10.4": ["pirlo"], "1.1 -4.8 14.0": ["aquafit"], "2.7 4.9 5.8": ["gare"], "1.8 -1.1 1.8": ["cancell"], "24.1 10.6 21.6": ["woodchop"], "-3.2 24.4 3.3": ["resiling"], "9.6 9.0 19.4": ["jala"], "11.3 -1.3 13.7": ["replated"], "-5.3 -4.5 -4.1": ["hange"], "2.0 6.9 11.4": ["malnutritioned"], "10.2 -1.0 9.5": ["methcathinone"], "-1.5 16.5 5.8": ["germicides"], "16.9 18.9 19.4": ["uark"], "11.5 1.1 4.2": ["oston"], "6.7 12.1 1.8": ["wolfram"], "-0.1 -0.1 1.0": ["stipendiary"], "14.0 37.7 12.5": ["wanzer"], "9.0 0.3 4.5": ["wehn"], "12.8 3.0 14.6": ["tighteners"], "6.3 15.3 15.1": ["comeout"], "16.3 12.0 29.8": ["lavosh"], "-3.0 22.4 1.9": ["suspectible"], "5.4 7.8 37.5": ["billfishing"], "9.5 15.8 20.6": ["randiness"], "15.2 -1.7 2.0": ["microseries"], "5.3 7.6 12.5": ["headguards"], "4.1 4.5 4.7": ["reinstitutes"], "-6.3 25.8 -1.9": ["intrusted"], "7.3 11.8 10.9": ["tixs"], "5.0 19.5 18.1": ["magister"], "4.4 7.0 10.8": ["cpmaz"], "19.4 17.7 2.6": ["bootroom"], "8.8 5.2 16.5": ["poc"], "3.8 14.5 6.0": ["induna"], "3.1 11.7 4.7": ["normativity"], "-6.4 0.0 15.2": ["roth"], "6.3 -2.0 21.6": ["coladas"], "7.3 9.7 12.8": ["thirdman"], "15.7 -7.3 2.0": ["hackathons"], "1.4 9.2 19.0": ["suerte"], "7.2 16.3 10.9": ["fogeyish"], "7.1 1.7 7.6": ["prepurchased"], "-0.3 4.5 5.0": ["erythematosus"], "-2.0 8.6 9.6": ["impecable"], "7.2 -4.2 -0.9": ["philanthrophy"], "21.3 11.2 3.5": ["fussball"], "9.0 3.8 4.7": ["neuromodulator"], "11.1 4.9 14.9": ["shoeshiner"], "23.8 3.5 10.5": ["toyshops"], "10.0 18.4 6.1": ["gasmasks"], "0.5 16.1 6.2": ["disjunctions"], "5.3 10.7 8.6": ["highy"], "7.9 -2.9 2.3": ["eyetracking"], "-6.5 8.1 -6.1": ["eneral"], "-2.9 11.1 9.8": ["theek"], "-7.2 4.9 2.5": ["financialperformance"], "10.6 13.3 -0.4": ["redirectors"], "12.2 7.9 9.6": ["guildhall"], "-8.1 3.5 4.6": ["osteopenic"], "3.2 -1.8 -2.9": ["youe"], "4.1 -1.7 -8.7": ["neuromonitoring"], "10.8 8.1 11.4": ["necesita"], "-1.7 4.6 0.9": ["timesavings"], "12.6 2.8 7.8": ["bioclimatic"], "9.3 21.1 9.6": ["tweedledee"], "17.3 12.6 16.4": ["grinchy"], "9.5 4.3 12.0": ["dualie"], "8.5 11.7 39.6": ["whimbrels"], "19.8 18.8 27.8": ["blowdryer"], "1.7 18.3 10.1": ["paty"], "5.1 12.9 10.5": ["seni"], "19.2 17.0 23.6": ["sicky"], "1.4 2.2 3.6": ["culminations"], "3.4 -0.0 11.7": ["nonjuried"], "-3.8 1.7 3.4": ["acl"], "7.9 14.8 31.2": ["zesting"], "18.0 18.5 14.1": ["fud"], "-0.8 5.7 11.6": ["alcoholrelated"], "14.4 8.6 7.6": ["berks"], "6.5 4.5 9.3": ["momager"], "-0.7 8.5 12.6": ["demineralisation"], "13.3 12.0 10.7": ["gyming"], "2.2 9.1 5.8": ["vaste"], "0.1 7.3 11.2": ["undebated"], "12.6 9.2 23.8": ["inlands"], "14.9 17.1 10.4": ["meritocrats"], "9.7 0.1 3.8": ["credi"], "7.8 23.9 15.3": ["sterotypical"], "0.3 12.0 3.3": ["recompleting"], "5.3 18.2 -0.2": ["cryptanalysts"], "-1.4 5.3 12.7": ["daya"], "16.3 12.5 17.2": ["kachina"], "11.0 1.2 10.9": ["ampule"], "-5.1 11.8 8.8": ["resurveying"], "12.3 -0.7 9.4": ["versione"], "15.3 13.1 23.7": ["acidy"], "16.9 -4.4 8.3": ["appliers"], "19.5 36.0 22.6": ["energon"], "2.4 8.8 17.2": ["collodion"], "1.6 8.2 -2.3": ["disabuses"], "6.4 26.7 -0.6": ["secularising"], "-8.8 10.6 4.2": ["emphasing"], "4.8 19.1 11.0": ["nonflying"], "0.9 -5.1 -2.5": ["intitled"], "2.3 4.8 27.6": ["nyjer"], "16.7 16.0 8.5": ["consipiracy"], "1.0 2.7 22.9": ["texel"], "-1.2 0.8 10.3": ["ghandu"], "9.8 13.8 11.9": ["linebreak"], "4.7 15.0 13.1": ["bastardy"], "7.6 4.0 3.4": ["taining"], "8.2 10.8 18.3": ["dago"], "0.6 9.3 7.1": ["ecovillages"], "16.2 3.9 35.7": ["bruschettas"], "-0.8 12.1 -5.1": ["crticised"], "11.6 -0.3 8.1": ["adire"], "18.7 13.9 6.1": ["backgound"], "7.3 6.6 0.4": ["recordbook"], "4.7 17.0 12.2": ["discourteously"], "12.1 10.3 14.6": ["coreldraw"], "15.4 5.8 35.4": ["ichthyologists"], "14.0 27.5 21.8": ["belowdecks"], "6.6 22.6 5.8": ["helicoper"], "10.6 2.2 10.4": ["tontine"], "13.7 12.1 13.5": ["flutterings"], "6.9 11.3 4.3": ["handgrenade"], "9.2 1.2 16.0": ["melanie"], "0.3 7.0 9.5": ["laughathon"], "2.1 13.1 10.3": ["centromeric"], "13.8 14.6 6.9": ["undermotivated"], "2.5 0.9 16.2": ["hite"], "1.7 0.2 3.9": ["relys"], "6.1 19.5 11.6": ["preliterate"], "6.9 20.0 10.7": ["undermatched"], "8.0 31.1 7.4": ["targeters"], "1.3 7.5 18.7": ["gamit"], "-7.6 12.9 -3.6": ["connectional"], "-2.8 9.2 15.8": ["phylloquinone"], "0.8 10.8 10.9": ["homophily"], "3.9 4.5 0.6": ["scenographer"], "-2.1 24.1 3.2": ["mitzvoth"], "4.5 4.8 13.6": ["quiltmaker"], "1.7 17.8 22.6": ["lambsquarters"], "13.8 3.1 5.8": ["altogther"], "8.7 7.3 16.5": ["knoxville"], "0.2 10.7 7.7": ["whas"], "17.0 17.2 18.6": ["throatily"], "27.4 32.9 22.3": ["gryphons"], "11.9 12.3 32.1": ["confiture"], "12.9 12.8 11.3": ["doujin"], "-1.3 6.1 10.0": ["adenoid"], "9.0 6.0 7.3": ["eens"], "6.4 30.6 6.1": ["antistate"], "13.4 12.0 29.1": ["inuksuit"], "5.0 3.6 6.3": ["enn"], "2.0 22.0 9.8": ["manoeuverability"], "10.8 -4.7 4.7": ["mardi"], "7.1 10.4 18.2": ["kanu"], "11.2 4.4 8.5": ["pullman"], "-4.3 10.2 6.4": ["antiestrogen"], "-9.2 11.1 8.5": ["hypercapnia"], "6.8 8.9 7.1": ["rect"], "14.0 7.7 12.5": ["rhythmless"], "-5.3 5.8 15.8": ["opportunitites"], "11.7 8.5 10.2": ["earthship"], "1.7 5.0 11.5": ["kaz"], "19.1 5.7 18.4": ["ropelike"], "13.8 5.2 34.7": ["cinammon"], "-1.1 9.6 12.2": ["nonveteran"], "13.6 -2.3 9.1": ["teenies"], "2.8 -0.3 7.3": ["beverly"], "10.9 19.9 5.0": ["waterbombing"], "4.1 12.1 10.7": ["aane"], "16.7 23.7 14.4": ["kkr"], "11.8 27.1 9.0": ["napalming"], "-1.2 15.4 10.2": ["sshd"], "8.0 1.9 18.0": ["acuminata"], "9.6 26.9 13.6": ["rpgs"], "-7.3 -2.4 6.0": ["housetypes"], "5.9 4.8 12.1": ["videocards"], "11.5 14.6 8.3": ["srsly"], "8.8 11.1 12.7": ["shorthands"], "-4.6 13.9 5.0": ["traumatization"], "6.0 5.1 -0.9": ["gheraoing"], "9.4 14.7 14.0": ["strokeless"], "9.3 5.5 13.2": ["significa"], "6.8 11.5 11.3": ["idlings"], "4.7 20.7 25.0": ["ifit"], "7.9 21.6 19.7": ["turgidity"], "16.4 9.1 40.1": ["salmonberries"], "8.8 4.7 14.1": ["mexicanos"], "12.5 20.5 15.8": ["alkie"], "23.9 10.8 18.6": ["ribbony"], "9.8 18.7 3.7": ["dragooning"], "21.8 17.1 5.0": ["openable"], "8.7 8.8 7.1": ["multiverses"], "14.1 10.1 16.9": ["poochy"], "5.3 2.3 13.7": ["phenomonal"], "4.0 6.4 10.9": ["puckishness"], "-0.3 5.8 13.5": ["marasmus"], "17.6 26.7 19.0": ["hookshot"], "-2.5 3.5 1.7": ["ashish"], "19.8 7.7 5.4": ["commericials"], "27.3 15.1 24.9": ["paramecia"], "9.1 24.6 13.9": ["gamesman"], "6.1 3.6 0.8": ["barrelman"], "6.5 0.8 7.8": ["premie"], "9.5 11.2 9.4": ["initialisms"], "2.2 15.9 2.1": ["chessplayer"], "5.1 0.4 13.6": ["snl"], "-0.6 3.5 3.7": ["yourlife"], "9.2 13.2 9.6": ["globulins"], "5.3 -3.3 -3.6": ["areport"], "14.5 8.6 22.5": ["heathery"], "17.5 29.3 17.8": ["valkyrie"], "2.2 20.5 9.0": ["nonpersons"], "5.3 -4.7 2.5": ["professsional"], "4.4 7.9 16.3": ["xejn"], "16.0 1.5 39.4": ["fregola"], "1.4 3.9 6.3": ["mikvahs"], "9.5 8.0 9.2": ["supples"], "17.8 6.3 15.8": ["threepence"], "14.9 13.6 26.3": ["beaners"], "9.4 11.4 34.7": ["jackfruits"], "1.9 5.4 7.8": ["chromatograms"], "3.3 13.2 15.7": ["actornaught"], "9.0 1.6 20.0": ["swannery"], "19.5 13.4 42.9": ["ptarmigans"], "4.6 5.0 34.4": ["vitellogenin"], "4.2 2.7 9.0": ["ashton"], "8.4 4.9 0.6": ["facinated"], "3.8 14.6 9.0": ["galat"], "3.9 -2.3 -5.3": ["goles"], "1.4 5.3 3.7": ["natak"], "4.7 10.5 -1.5": ["polltakers"], "7.2 9.0 24.0": ["sinn"], "3.6 6.1 19.8": ["deodorised"], "7.2 31.2 -1.6": ["landguards"], "11.6 10.6 27.0": ["lolli"], "8.4 0.2 3.8": ["etween"], "-1.1 1.4 5.4": ["isomerase"], "8.9 15.5 14.9": ["prissily"], "5.5 4.3 5.8": ["cavernoma"], "0.9 20.4 17.1": ["divisors"], "-3.9 0.1 5.4": ["retropubic"], "6.5 29.9 19.6": ["inexactitude"], "-0.8 -4.0 -0.8": ["sesason"], "12.9 21.5 19.6": ["pareidolia"], "22.9 17.4 15.5": ["blacklights"], "8.3 -2.0 -0.1": ["plast"], "5.5 15.0 2.7": ["churchill"], "15.1 8.4 2.5": ["megafirms"], "17.5 7.5 18.5": ["doonas"], "23.5 18.9 9.3": ["cogwheel"], "15.7 8.8 10.7": ["gasper"], "16.0 21.0 25.0": ["defoliates"], "7.0 2.3 -4.1": ["insiderish"], "15.9 13.9 26.6": ["bluejay"], "10.0 9.9 13.8": ["ellipsoids"], "1.1 19.1 3.6": ["theparty"], "3.2 17.8 14.2": ["meliorate"], "16.4 1.1 18.9": ["safeway"], "2.4 -4.0 -0.6": ["possbile"], "14.4 7.2 25.8": ["rufus"], "9.4 8.9 3.7": ["gasifies"], "12.9 21.1 5.5": ["forumites"], "-0.9 -3.5 1.6": ["domus"], "22.9 14.4 38.5": ["waxworm"], "0.4 14.9 5.0": ["destigmatizing"], "7.2 10.7 19.8": ["rud"], "-1.3 -8.8 6.1": ["prebid"], "12.1 14.2 9.0": ["inartistic"], "9.5 18.3 17.4": ["dunkings"], "11.9 6.8 17.4": ["bumbag"], "5.5 -0.3 2.0": ["andalso"], "1.3 -3.6 7.0": ["sandiego"], "11.8 19.8 6.4": ["defectiveness"], "6.8 20.7 19.0": ["mauri"], "11.4 9.4 28.4": ["mouthwateringly"], "3.0 6.2 4.4": ["impo"], "-5.7 11.3 -1.6": ["thienopyridines"], "-3.9 12.9 6.0": ["crewchief"], "3.2 17.8 15.7": ["wishy"], "1.3 18.4 13.8": ["plotwise"], "12.8 12.7 24.4": ["phu"], "1.6 8.5 9.6": ["polymyalgia"], "1.2 7.6 9.6": ["wase"], "5.5 11.7 13.9": ["akhada"], "3.3 2.5 14.2": ["otoplasty"], "6.8 14.7 6.8": ["unlegislated"], "4.9 17.9 4.5": ["nontheist"], "2.1 -8.9 -1.5": ["recomends"], "16.3 11.8 9.1": ["arsing"], "12.2 10.4 11.8": ["deus"], "-2.3 11.6 4.8": ["tosay"], "7.6 5.6 0.5": ["affils"], "6.3 2.8 18.1": ["preadipocytes"], "-3.8 11.8 8.9": ["enskinment"], "0.2 6.8 8.3": ["hypokalaemia"], "3.7 14.7 11.6": ["kaiwai"], "12.1 -3.5 -1.0": ["collateralise"], "11.0 10.8 30.1": ["cordylines"], "12.5 6.5 2.5": ["initiatve"], "9.6 21.8 5.8": ["philander"], "-4.1 8.0 6.8": ["myoma"], "8.5 8.3 15.3": ["allt"], "-0.4 19.6 -2.0": ["importan"], "-4.6 -3.7 -9.8": ["leter"], "9.4 9.7 13.5": ["unneighbourly"], "15.5 1.2 33.6": ["steakburger"], "2.1 2.4 5.9": ["elly"], "-3.8 8.2 5.0": ["macrocycle"], "1.7 -8.4 6.9": ["anager"], "-1.5 16.5 8.7": ["poeticize"], "7.9 -1.8 8.4": ["humana"], "1.1 8.2 7.2": ["cfe"], "20.1 3.7 5.5": ["contracters"], "14.5 17.7 16.4": ["burglers"], "1.3 4.5 4.8": ["midmost"], "15.8 13.4 16.9": ["whoooo"], "6.8 4.2 5.0": ["thiodiglycol"], "1.1 11.5 3.1": ["chemisorption"], "11.3 25.2 7.2": ["militamen"], "6.1 9.2 7.3": ["managementand"], "8.6 9.3 8.6": ["sinkerballing"], "1.7 22.7 11.7": ["smugglings"], "17.9 0.6 16.8": ["epiwafer"], "1.6 -1.0 13.2": ["fibroma"], "-1.7 -0.1 13.1": ["vated"], "9.7 6.7 47.0": ["beeliners"], "15.9 13.3 2.1": ["mericans"], "-5.8 2.9 3.8": ["oestrogenic"], "2.1 10.0 19.2": ["glutamates"], "5.2 8.8 5.0": ["focusedon"], "16.7 20.0 14.6": ["frustratedly"], "1.1 17.0 9.0": ["feminisms"], "17.3 5.6 13.6": ["supertight"], "7.2 -2.7 8.9": ["milyon"], "11.0 7.3 5.7": ["aurait"], "11.8 19.1 8.4": ["shhhhhh"], "-1.0 2.1 10.4": ["umaga"], "-0.3 22.6 13.0": ["abillity"], "3.7 7.9 7.3": ["deoxy"], "10.6 8.3 9.1": ["partidos"], "3.7 1.7 16.8": ["twofers"], "-3.8 -0.7 3.8": ["andher"], "12.9 20.1 8.2": ["immunoadhesins"], "1.0 -3.6 -0.2": ["frs"], "5.9 3.7 5.8": ["countertrade"], "-3.8 12.5 7.2": ["thrombogenic"], "-3.2 8.2 15.3": ["vestryman"], "13.1 17.2 9.8": ["lightwaves"], "1.6 7.4 9.1": ["regualar"], "12.7 18.3 7.9": ["handwringers"], "8.8 32.0 7.4": ["nuclearised"], "12.6 15.2 6.9": ["luckly"], "9.6 23.7 14.4": ["slaughtermen"], "2.2 11.6 7.1": ["organizationwide"], "13.0 18.8 9.5": ["isotherms"], "6.5 24.3 11.5": ["anythng"], "11.2 15.8 4.9": ["buffon"], "1.3 -1.6 6.5": ["originale"], "9.3 15.2 20.1": ["rockhound"], "6.5 8.1 6.1": ["acyclic"], "-1.6 6.8 6.4": ["retabulated"], "-1.4 5.0 2.2": ["departmentalization"], "0.4 16.3 9.3": ["provincemates"], "13.1 11.1 15.5": ["eyebrowed"], "-0.4 10.4 14.5": ["mononuclear"], "5.9 10.8 9.3": ["chota"], "-0.8 -1.7 11.8": ["achos"], "6.8 7.1 15.9": ["veery"], "-6.8 12.6 16.2": ["overappropriated"], "8.4 18.7 11.3": ["ickiest"], "4.7 0.7 4.6": ["cryosurgical"], "-4.3 2.3 0.9": ["azelastine"], "-0.3 8.6 16.7": ["mereka"], "17.8 15.2 12.2": ["lavs"], "-2.5 7.5 6.7": ["nonmusicians"], "17.3 9.1 11.3": ["tessellations"], "7.7 6.6 15.0": ["stainable"], "11.2 1.7 26.7": ["huller"], "12.9 10.5 38.1": ["kataifi"], "13.3 1.2 39.4": ["bhuna"], "12.6 10.0 5.8": ["reweaving"], "6.1 2.4 -8.6": ["syskoplan"], "-2.2 2.0 0.1": ["benzonatate"], "4.7 0.3 1.3": ["deanships"], "8.7 30.5 14.6": ["capitulatory"], "22.0 14.0 27.5": ["stingless"], "-4.2 9.2 5.8": ["hyperintensity"], "0.4 18.4 0.8": ["crticism"], "18.7 14.5 18.0": ["pretzeled"], "-1.2 8.5 10.2": ["reck"], "2.9 9.3 18.2": ["awdi"], "13.9 7.7 7.9": ["maudit"], "17.2 9.8 44.2": ["scorpionfish"], "14.0 10.7 13.9": ["seraglio"], "17.8 13.4 17.0": ["relicts"], "4.0 2.4 20.2": ["bere"], "11.6 -0.3 13.2": ["bubbleheaded"], "-4.8 21.5 3.4": ["infightings"], "22.2 7.5 30.6": ["superchilled"], "13.8 12.3 20.6": ["muerto"], "11.7 8.2 -1.5": ["draughting"], "15.6 18.3 25.0": ["sinistral"], "4.0 2.5 18.6": ["rester"], "11.4 5.1 15.6": ["nollie"], "8.7 4.5 27.4": ["citruses"], "14.8 25.2 12.7": ["blabby"], "25.1 -8.6 -3.2": ["basd"], "-7.3 4.6 4.7": ["mukhda"], "4.4 0.9 0.9": ["prorates"], "7.2 18.7 3.1": ["convinient"], "11.0 11.5 12.8": ["geoneutrinos"], "-0.9 -1.8 7.2": ["occupany"], "5.0 14.1 7.0": ["subthemes"], "13.2 16.8 20.0": ["archetypally"], "5.6 2.9 -3.3": ["releasd"], "9.3 -1.4 1.7": ["tongiht"], "1.0 26.6 15.2": ["larvacides"], "4.2 9.4 11.8": ["oppertunities"], "20.5 -2.5 41.2": ["portabello"], "-7.2 17.5 -0.0": ["naove"], "-0.6 31.2 1.1": ["spetsnaz"], "5.1 10.5 9.5": ["pipettor"], "-1.9 5.7 4.2": ["mutism"], "4.0 5.3 6.7": ["resul"], "10.2 7.9 8.5": ["tranced"], "-6.9 9.9 5.8": ["imposable"], "8.2 7.5 30.2": ["vadai"], "16.4 13.2 27.4": ["ganoderma"], "8.9 4.4 16.6": ["methamphetimine"], "13.0 21.2 9.4": ["tweedledum"], "11.9 6.9 14.0": ["buckers"], "8.6 10.3 -1.5": ["waterblasters"], "10.2 12.5 26.0": ["powerhead"], "11.2 10.1 15.6": ["lookit"], "16.0 -7.7 -3.5": ["headquarterd"], "3.5 13.2 -0.2": ["unpunctual"], "1.3 2.4 1.5": ["mri"], "17.4 21.1 13.6": ["irrestible"], "19.4 20.3 10.9": ["enviromentalists"], "0.7 15.5 0.2": ["dittoed"], "5.5 -0.7 12.6": ["metakaolin"], "8.0 11.6 2.6": ["sequestrations"], "15.1 5.7 7.2": ["atmostphere"], "9.6 28.6 2.3": ["antichrists"], "7.4 3.9 12.4": ["hectre"], "8.6 6.7 19.1": ["outwash"], "6.0 8.1 9.7": ["rajesh"], "9.7 9.0 18.7": ["algaecides"], "-5.2 5.3 7.2": ["teve"], "5.6 19.7 5.6": ["deperate"], "6.4 19.5 3.8": ["proctologists"], "-6.0 22.5 -9.7": ["leaderhip"], "12.0 19.5 20.3": ["spaniard"], "6.4 16.6 13.7": ["disequilibria"], "0.6 9.5 14.5": ["maayos"], "8.3 23.7 0.5": ["teleguided"], "10.6 11.7 6.8": ["counterpointing"], "5.4 5.1 4.6": ["multiplanar"], "3.4 9.3 7.1": ["overpronation"], "10.1 10.3 7.9": ["sharding"], "16.5 13.8 21.9": ["tanktops"], "4.5 -2.1 2.8": ["ijarah"], "3.8 15.8 0.0": ["ecurity"], "2.7 20.1 8.2": ["bhakt"], "13.3 -2.1 15.1": ["sonoma"], "-2.4 8.9 9.7": ["gallate"], "7.0 4.1 6.3": ["macrocycles"], "14.8 11.4 8.8": ["reflectorized"], "6.4 6.0 11.2": ["palabra"], "5.1 0.9 17.5": ["pobl"], "11.0 1.3 10.5": ["xinmsn"], "8.3 8.8 14.0": ["redolence"], "0.1 15.1 10.6": ["detraining"], "6.9 11.8 19.7": ["pearlers"], "12.7 9.7 3.3": ["allroad"], "4.0 1.4 3.8": ["concurso"], "-2.4 8.1 16.2": ["ngai"], "-8.4 -2.1 1.5": ["diskectomy"], "12.0 7.3 1.2": ["sportstars"], "-0.2 8.3 4.4": ["sigheh"], "0.6 5.7 11.0": ["colorbearer"], "13.2 -1.1 18.6": ["broomcorn"], "16.3 13.6 -0.5": ["ultradense"], "-10.1 26.7 8.0": ["emunah"], "1.5 3.6 5.5": ["sportsdesk"], "8.6 1.9 3.5": ["subsecretary"], "-2.7 13.4 1.1": ["othere"], "9.1 7.7 3.6": ["arebeing"], "7.4 25.3 6.8": ["afront"], "-6.3 12.0 8.4": ["alowing"], "6.3 8.5 13.0": ["plaisir"], "-0.8 9.2 -1.2": ["addes"], "1.9 1.2 9.9": ["racemares"], "3.3 9.5 4.8": ["interexchange"], "18.2 2.4 19.7": ["megacasino"], "16.3 2.5 34.7": ["duxelles"], "5.0 5.7 17.5": ["peda"], "13.0 -1.7 4.6": ["musicvideo"], "-1.7 16.8 -0.8": ["certainity"], "-7.0 13.5 11.3": ["rememberd"], "1.1 6.6 26.4": ["kinno"], "10.3 7.2 23.5": ["gordo"], "-4.2 11.4 16.8": ["changquan"], "4.0 11.5 20.5": ["guvs"], "19.7 16.9 14.5": ["hogger"], "5.7 3.8 12.1": ["moonmen"], "11.9 -0.5 3.9": ["biomechanists"], "11.2 3.1 26.7": ["dogtooth"], "1.6 2.3 8.8": ["uconn"], "3.4 4.4 10.6": ["lsd"], "5.4 4.6 17.3": ["tabac"], "15.3 11.1 24.6": ["cluckers"], "-0.0 11.9 8.1": ["rectus"], "19.9 28.0 20.2": ["maneaters"], "11.9 13.3 10.2": ["unlocated"], "6.3 1.4 7.7": ["xfactor"], "9.3 20.5 2.5": ["semed"], "4.5 21.5 8.7": ["sympa"], "0.4 -5.9 17.3": ["jui"], "17.2 28.5 19.8": ["whirlybirds"], "-8.5 6.4 2.7": ["bochurim"], "13.9 13.5 22.0": ["prosimians"], "9.9 19.7 6.1": ["romanticists"], "-1.0 13.6 11.9": ["mucocutaneous"], "10.2 10.2 45.5": ["luderick"], "13.2 1.8 17.3": ["gnar"], "2.8 22.3 2.7": ["broder"], "9.8 1.9 10.4": ["patternmaking"], "7.8 28.5 17.3": ["animality"], "4.7 -3.5 9.9": ["bubblier"], "5.6 3.5 8.8": ["kays"], "6.0 4.0 8.6": ["relitigated"], "11.5 14.9 6.2": ["spastics"], "-3.7 1.7 15.5": ["contractuals"], "6.2 10.5 3.4": ["decompiled"], "-2.2 11.7 1.9": ["dissapearance"], "3.2 6.7 8.7": ["arlington"], "6.6 -4.6 2.9": ["witrh"], "14.9 10.0 17.2": ["delic"], "6.2 1.4 19.8": ["unweaned"], "28.7 10.3 16.8": ["shrinker"], "-5.4 18.4 5.6": ["precipitants"], "10.2 20.6 1.2": ["singlemindedly"], "-1.3 13.5 1.7": ["reparability"], "1.2 10.9 19.0": ["betadine"], "8.6 9.6 15.0": ["fanlight"], "15.0 10.7 36.4": ["tideline"], "15.5 6.4 15.2": ["omic"], "8.1 7.3 7.3": ["secong"], "0.8 -0.7 -0.0": ["procuratorial"], "10.8 16.2 24.4": ["caryopteris"], "0.9 1.5 1.3": ["graphologists"], "3.6 -3.8 -3.7": ["rsf"], "2.1 7.9 9.7": ["bagi"], "9.8 -4.3 -4.7": ["equinet"], "-4.0 3.0 10.8": ["masteral"], "-2.3 3.1 8.4": ["datukship"], "10.6 -3.4 15.9": ["minicasino"], "12.1 1.6 16.6": ["appoggiatura"], "8.7 20.0 3.0": ["responsibity"], "3.0 -2.8 -3.5": ["ideated"], "20.0 14.7 27.5": ["saltpan"], "-3.6 32.0 0.9": ["nonkinetic"], "9.8 2.1 19.2": ["hottub"], "12.0 21.6 8.6": ["unsuppressed"], "6.6 15.0 14.6": ["perseveration"], "11.3 9.8 33.1": ["subadult"], "10.6 3.8 13.9": ["suncatcher"], "2.6 8.9 14.3": ["nieghborhood"], "11.5 16.0 10.7": ["puch"], "4.4 23.5 -2.8": ["intellection"], "8.3 -2.4 8.0": ["investi"], "16.8 5.8 -1.0": ["flashest"], "10.2 2.7 1.8": ["entrepre"], "9.7 8.1 10.0": ["kwela", "heptathlons"], "12.5 19.8 14.8": ["tecnicos"], "-3.9 -3.8 0.5": ["accessioned"], "4.0 18.8 10.1": ["instinctiveness"], "6.1 28.2 4.2": ["slavishness"], "2.5 14.1 1.7": ["govermental"], "8.7 -5.1 -6.0": ["conferenc"], "15.4 9.9 28.5": ["larkspurs"], "5.8 8.4 12.2": ["seladang"], "8.3 16.2 22.5": ["mithais"], "6.7 0.2 0.9": ["calciner"], "20.0 6.3 37.3": ["aebleskiver"], "11.5 8.8 7.1": ["oooooo"], "8.0 15.7 16.3": ["kaingin"], "0.3 10.6 8.0": ["thetotal"], "4.4 16.1 11.3": ["caesura"], "10.5 9.3 13.9": ["rightsized"], "-4.7 8.6 6.0": ["ignor"], "4.2 4.7 11.1": ["multithread"], "2.6 13.9 11.2": ["sluttiest"], "18.9 19.2 14.3": ["galoots"], "5.2 6.2 23.4": ["unmilled"], "4.5 13.1 15.5": ["postback"], "0.8 11.5 2.3": ["supertiebreaker"], "12.9 11.8 1.5": ["relights"], "8.0 14.1 18.9": ["smectite"], "3.2 8.9 9.8": ["palytoxin"], "6.8 4.0 4.9": ["duranguense"], "2.4 8.0 3.5": ["itsmy"], "8.5 11.9 14.6": ["woulds"], "23.2 5.1 4.6": ["empresario"], "6.0 19.3 3.8": ["coglioni"], "3.8 -0.1 6.7": ["prive"], "5.9 15.0 10.2": ["cortexes"], "8.6 18.2 0.5": ["eath"], "24.6 8.0 18.0": ["swaybacked"], "1.0 13.2 18.1": ["sukka"], "22.6 7.9 14.5": ["terracota"], "-2.8 6.3 -1.6": ["graduants"], "-1.5 6.4 0.9": ["aza"], "13.8 13.8 44.3": ["phalaropes"], "19.9 10.6 23.4": ["jem"], "16.9 3.7 6.8": ["stic"], "20.1 10.8 26.5": ["spiraea"], "9.4 11.7 13.3": ["vixenish"], "-6.2 13.4 6.6": ["noncareer"], "13.1 4.2 15.6": ["artsier"], "0.7 10.4 25.8": ["renourishing"], "10.9 20.0 7.3": ["demolisher"], "20.3 15.2 15.2": ["activision"], "9.9 17.5 9.5": ["culturalism"], "16.5 3.4 14.6": ["unsatiated"], "8.2 19.3 1.5": ["powermen"], "14.3 14.9 3.9": ["condensations"], "2.3 6.4 1.9": ["cials"], "-2.0 21.6 7.2": ["kohen"], "14.8 8.2 28.6": ["rugosa"], "12.6 10.3 16.7": ["paanch"], "2.4 4.9 17.3": ["asists"], "13.7 20.2 28.3": ["spindrift"], "8.6 6.5 8.0": ["tragi"], "1.1 -0.0 -3.7": ["initital"], "2.5 12.5 15.0": ["wefts"], "3.7 -4.3 10.8": ["upticked"], "9.8 18.6 12.3": ["swining"], "2.7 2.7 -4.6": ["neuroanatomist"], "-6.4 16.6 4.1": ["onlt"], "10.9 11.3 2.5": ["transalpine"], "5.5 5.9 5.4": ["porfolios"], "17.7 2.4 10.0": ["technitium"], "-0.4 -0.7 0.2": ["webshow"], "1.7 4.7 -0.9": ["thts"], "0.1 -4.4 14.6": ["vals"], "7.5 3.7 6.6": ["venezolano"], "10.8 2.2 8.3": ["mfr"], "10.4 14.5 11.3": ["capsuled"], "10.6 16.6 10.0": ["windstream"], "16.5 3.4 6.8": ["signiture"], "7.4 2.9 9.2": ["dysesthesia"], "23.7 2.5 -1.1": ["crowdsources"], "15.7 14.3 8.2": ["vectorized"], "8.9 13.0 8.9": ["gamest"], "12.7 6.4 29.7": ["kachori"], "-10.5 2.3 9.8": ["tbnewswatch"], "23.8 -5.4 10.7": ["shelfs"], "14.0 15.2 22.2": ["terrestris"], "9.3 8.2 23.1": ["masting"], "12.5 1.9 23.3": ["figgy"], "4.4 0.8 14.3": ["wneud"], "-3.3 2.4 8.8": ["ganaxolone"], "6.2 15.0 9.2": ["yawningly"], "-1.6 -5.0 -1.4": ["acs"], "5.3 3.9 4.9": ["filiming"], "15.1 11.6 5.7": ["welshing"], "3.1 7.9 1.5": ["aarp"], "6.2 3.7 8.2": ["competititon"], "13.3 0.5 -3.0": ["fraudently"], "-0.1 10.1 -1.9": ["concertation"], "11.7 11.9 38.5": ["dewberry"], "18.9 7.5 16.7": ["anchorless"], "7.9 25.2 4.6": ["mendacities"], "14.4 9.1 19.6": ["bupkus"], "5.5 23.7 19.2": ["bodyshot"], "6.5 23.7 7.4": ["whishes"], "14.3 6.3 23.8": ["scarlets"], "15.6 18.3 17.3": ["huricanrana"], "16.6 12.7 22.8": ["hankerchief"], "-0.4 23.4 3.9": ["arrestment"], "10.5 13.9 19.2": ["sonnen"], "16.3 37.1 15.1": ["killstreak"], "27.5 10.7 -4.8": ["truckmaking"], "2.9 4.8 5.0": ["guildelines"], "11.4 12.8 16.1": ["huuuuge"], "-1.8 -9.2 1.5": ["sumbit"], "16.3 11.6 18.3": ["minter"], "5.7 16.4 13.8": ["backheader"], "-0.9 5.4 8.3": ["deewana"], "17.0 20.0 10.1": ["stoniest"], "8.6 9.9 23.8": ["roundings"], "4.4 18.8 6.0": ["momenta"], "-3.6 7.6 9.1": ["cardiogenic"], "8.1 2.6 18.6": ["dover"], "12.5 4.4 2.8": ["callcentre"], "-6.3 2.2 6.4": ["diaphyseal"], "6.0 28.3 9.0": ["racisms"], "-2.6 11.7 13.0": ["metolachlor"], "14.9 9.2 29.3": ["mumbo"], "-3.5 4.5 4.0": ["unreferenced"], "6.4 13.4 11.6": ["shapelessness"], "5.0 12.7 1.5": ["mawkishly"], "15.2 7.9 6.8": ["cheapos"], "7.8 20.7 1.8": ["survivial"], "16.0 -3.1 5.6": ["powerstation"], "1.9 6.3 3.8": ["toutes"], "5.3 3.1 -1.2": ["reshufflings"], "-0.2 -2.5 7.6": ["blendstocks"], "1.4 11.5 9.4": ["predicitions"], "12.9 22.9 17.9": ["underhooked"], "9.6 4.7 17.7": ["petra"], "3.1 -3.4 4.4": ["restylane"], "-7.7 18.0 -2.5": ["deductively"], "-9.4 4.7 6.9": ["chaged"], "2.4 7.4 9.5": ["havana"], "2.0 8.6 4.3": ["gasbagging"], "6.5 8.7 8.4": ["archy"], "18.7 12.5 9.8": ["rorters"], "4.6 5.0 9.6": ["nakuha"], "0.8 1.5 11.6": ["premutation"], "5.9 1.2 4.9": ["serviceproviders"], "-14.1 -2.9 2.6": ["proctitis"], "13.8 10.6 0.7": ["celling"], "1.0 1.9 14.9": ["makikita"], "22.2 -0.3 9.8": ["housers"], "8.1 5.8 -3.8": ["superdistribution"], "15.0 4.2 21.7": ["choccies"], "-3.5 4.2 -9.7": ["caling"], "2.9 5.9 8.0": ["atic"], "18.2 12.4 5.8": ["shortsellers"], "10.4 4.2 9.6": ["bew"], "5.0 8.8 15.2": ["nontargeted"], "-1.8 12.8 5.8": ["drunkorexia"], "-4.5 16.1 0.2": ["openended"], "-0.5 19.8 7.2": ["objectivists"], "3.5 6.8 7.2": ["demultiplexing"], "13.2 11.6 6.0": ["absurb"], "10.8 -2.0 7.0": ["recal"], "12.9 22.3 11.9": ["overfriendly"], "7.3 3.9 11.9": ["hornfelsed"], "0.4 22.2 7.3": ["counterpose"], "17.7 14.5 19.2": ["gluepot"], "7.6 3.9 2.4": ["nontheatrical"], "10.3 11.2 4.7": ["caravilla"], "7.3 21.4 20.5": ["figger"], "8.0 15.9 7.4": ["unimprovable"], "5.0 9.7 4.9": ["neosoul"], "10.0 7.6 20.2": ["goodnatured"], "10.7 9.0 36.8": ["johnnycakes"], "6.4 14.6 4.8": ["somethig"], "2.7 15.8 4.3": ["othr"], "8.8 0.1 13.8": ["terpenoids"], "6.0 11.7 12.7": ["abyssmal"], "6.9 8.2 11.8": ["motorcycled"], "3.6 11.0 2.8": ["siropa"], "-4.8 1.1 -2.9": ["predialysis"], "13.3 18.9 14.3": ["jericho"], "7.5 15.0 1.2": ["superiorities"], "7.8 -7.0 14.0": ["tural"], "9.0 -0.4 9.7": ["sesquicentenary"], "13.7 0.8 30.5": ["creamware"], "1.9 2.4 9.6": ["samity"], "-3.5 4.3 6.1": ["maternities"], "10.9 12.5 20.0": ["hybridizes"], "6.6 19.3 11.6": ["asif"], "7.4 10.9 12.6": ["abang"], "-6.4 6.3 25.7": ["haors"], "9.7 11.1 21.8": ["ttt"], "-3.2 -3.5 2.8": ["onf"], "20.8 16.5 22.0": ["superweed"], "11.3 23.5 17.3": ["auteurism"], "6.6 12.8 -3.1": ["fornight"], "-7.5 4.8 3.8": ["vasopressors"], "7.8 27.1 8.3": ["jannat"], "16.2 11.5 21.4": ["laburnum"], "-8.6 -1.9 4.9": ["disbarments"], "20.1 10.6 7.6": ["scorebox"], "16.3 2.9 10.0": ["cossack"], "0.2 -1.2 4.4": ["lineworker"], "-0.4 21.4 20.3": ["mucoid"], "-11.3 3.8 6.5": ["ertapenem"], "3.1 6.5 7.5": ["biodrama"], "14.3 15.9 6.3": ["backslappers"], "17.2 11.5 12.5": ["sleazoid"], "2.7 2.0 13.7": ["saisons"], "18.1 18.1 6.8": ["centerless"], "7.3 1.8 15.1": ["aplite"], "7.6 1.8 19.4": ["oos"], "1.4 11.3 18.0": ["unroaded"], "19.3 12.6 19.3": ["prefabricate"], "11.6 8.6 3.5": ["scantron"], "4.6 6.1 14.2": ["mutta"], "6.3 -8.5 6.0": ["agricole"], "-3.2 11.9 6.7": ["amas"], "1.8 17.5 -3.1": ["jizyah"], "-6.1 3.1 1.5": ["supervisers"], "11.5 18.6 16.1": ["siderophore"], "9.5 10.4 19.5": ["wonderments"], "9.5 1.0 4.4": ["vnunet"], "10.4 6.1 17.8": ["tumuli"], "-5.5 1.0 10.4": ["epoxiconazole"], "15.5 14.4 10.0": ["chemcial"], "-5.4 -3.1 1.3": ["fater"], "-3.1 14.1 14.5": ["rishta"], "0.8 2.5 9.6": ["eliminee"], "-0.3 -0.0 8.9": ["sendout"], "-1.4 16.9 8.3": ["nonsupportive"], "-7.2 -5.2 2.7": ["flexability"], "1.9 11.8 4.1": ["jusy"], "-1.5 3.8 14.1": ["padam"], "4.3 -2.5 9.8": ["pase"], "8.1 4.0 2.4": ["prover"], "0.4 1.8 13.7": ["neurofibromin"], "24.4 11.4 16.8": ["rollergirls"], "-3.1 0.2 0.9": ["mammographers"], "17.1 12.5 4.1": ["haev"], "3.1 6.4 17.5": ["corpuses"], "7.2 9.2 17.0": ["kumaris"], "-3.6 7.6 6.1": ["teacherly"], "0.8 12.7 13.0": ["bearspread"], "-2.0 5.2 5.9": ["hypermobile"], "10.5 10.1 12.0": ["pantographs"], "9.1 2.0 30.0": ["kegged"], "6.4 5.7 16.9": ["headrace"], "3.1 7.3 -0.9": ["budiodarone"], "-2.4 7.1 17.2": ["seiyuu"], "6.3 9.2 9.7": ["caricaturized"], "0.0 15.2 10.1": ["poltiical"], "5.3 6.1 3.3": ["ille"], "5.0 9.9 11.8": ["sarcomeres"], "0.3 15.3 2.6": ["nonsensitive"], "-2.2 14.1 -2.9": ["rebutt"], "3.9 7.1 21.1": ["midpalate"], "10.8 16.5 9.9": ["stupified"], "18.7 10.4 3.6": ["spinmaster"], "21.4 17.5 17.4": ["megabudget"], "17.8 23.0 1.9": ["unfindable"], "18.0 11.3 20.2": ["burd"], "20.6 9.5 16.8": ["jackknifes"], "5.2 -8.1 2.7": ["availabl"], "4.1 1.1 -2.1": ["audiometer"], "14.2 8.5 6.0": ["ragnarok"], "6.5 2.7 1.7": ["printshops"], "4.4 11.9 22.9": ["mangia"], "7.8 9.8 13.1": ["dysfunctioning"], "20.6 23.5 15.9": ["truculently"], "13.8 16.6 8.2": ["fanart"], "2.2 22.4 -1.0": ["sorrowed"], "8.0 10.6 13.7": ["nightwatchmen"], "0.1 9.6 9.2": ["nonpoor"], "7.5 18.2 1.5": ["outboxes"], "6.1 0.6 7.9": ["environmen"], "23.3 7.0 23.7": ["waltzer"], "18.9 0.9 16.4": ["onionskin"], "23.8 6.2 6.9": ["unlaunched"], "11.6 33.0 15.2": ["templar"], "5.2 18.3 11.8": ["respectible"], "7.9 12.3 45.0": ["murre"], "8.3 5.6 2.7": ["businessy"], "1.9 9.3 15.7": ["kapatid"], "9.4 28.3 9.0": ["sieging"], "-3.8 10.2 4.8": ["colesevelam"], "22.3 18.9 12.5": ["moonlike"], "13.4 12.9 26.9": ["brier"], "-14.7 19.1 7.0": ["reenlistments"], "3.9 1.9 -1.0": ["farad"], "-1.4 12.4 1.0": ["untransferable"], "1.9 14.3 9.6": ["riffery"], "-1.0 18.7 3.0": ["hawza"], "0.7 0.7 2.9": ["backlogging"], "13.1 17.4 18.8": ["aaahhh"], "8.4 19.2 10.0": ["charlatanry"], "11.7 3.8 9.9": ["xinhua"], "6.4 16.7 10.9": ["fellahin"], "18.7 12.1 11.8": ["iets"], "6.6 6.4 7.6": ["embonpoint"], "7.6 8.3 10.2": ["paleobotanist"], "9.9 15.3 26.7": ["nobilis"], "-1.7 24.2 5.2": ["opponet"], "4.2 9.5 5.4": ["offfense"], "2.8 7.0 15.7": ["filches"], "-0.5 -7.8 7.9": ["cca"], "-0.0 5.2 18.8": ["nais"], "-0.6 12.8 0.6": ["madridista"], "-5.8 5.5 14.9": ["muth"], "20.3 10.8 15.8": ["skag"], "4.5 7.2 9.6": ["caveolin"], "2.5 8.7 -6.4": ["outgone"], "12.6 14.8 8.4": ["godd"], "18.7 13.3 29.4": ["treefrog"], "17.2 6.6 13.8": ["prezzo"], "-1.7 9.9 16.6": ["laurie"], "11.8 12.9 27.3": ["unfrosted"], "0.6 14.7 11.8": ["supersets"], "9.2 -1.1 6.6": ["recuitment"], "8.9 13.2 -2.1": ["amorphousness"], "7.5 4.9 9.7": ["openssl"], "-3.6 5.4 13.1": ["checkpointing"], "16.1 5.8 9.4": ["kangas"], "2.0 15.1 14.5": ["flintiness"], "-4.4 20.8 5.3": ["adminstrations"], "1.4 11.2 4.1": ["healthworkers"], "10.8 7.6 31.2": ["batteau"], "-0.4 20.8 2.0": ["activization"], "3.0 27.9 8.9": ["alaikum"], "5.9 9.3 21.6": ["kuku"], "11.3 12.2 11.2": ["figura"], "16.2 12.2 10.7": ["unfunniest"], "10.1 21.0 8.6": ["raillery"], "4.9 25.2 14.6": ["tatics"], "7.3 12.4 3.7": ["uncoached"], "-2.7 5.1 7.0": ["asssistant"], "-0.6 4.4 2.9": ["wol"], "6.8 -3.8 4.4": ["horspower"], "1.5 2.1 5.7": ["hyperlipemia"], "5.6 8.9 9.7": ["kothis"], "21.8 1.2 17.0": ["titted"], "12.7 0.4 12.8": ["netlinkblue"], "15.5 -0.5 21.3": ["multiwall"], "1.3 18.3 -2.7": ["misreports"], "-0.2 4.0 12.7": ["oomphy"], "-2.1 9.7 19.0": ["mamamayan"], "1.7 0.8 11.1": ["esi"], "9.2 11.3 22.9": ["nucleating"], "0.6 10.2 11.1": ["sewages"], "18.0 4.3 6.6": ["similair"], "10.5 16.0 2.9": ["furtherest"], "-0.6 8.1 0.6": ["channelers"], "2.1 13.0 10.0": ["arioso"], "6.9 15.3 9.4": ["economc"], "7.9 5.0 7.1": ["paxillin"], "5.3 4.4 12.3": ["shavee"], "12.3 1.4 12.8": ["skimpies"], "-10.1 12.0 -1.2": ["experianced"], "-0.7 4.2 9.6": ["swissie"], "0.7 0.6 2.2": ["upregulates"], "-2.1 5.1 7.3": ["bowdlerised"], "3.8 10.7 2.4": ["atttempt"], "9.3 4.6 9.0": ["hectoliter"], "18.8 8.8 21.7": ["monotreme"], "1.9 5.8 6.8": ["bila"], "-3.9 7.3 8.0": ["antiandrogen"], "10.9 12.4 24.6": ["gladioluses"], "11.1 10.1 17.3": ["bruk"], "7.4 11.6 5.4": ["wingnuttery"], "15.6 11.3 19.9": ["coolroom"], "2.4 11.2 13.3": ["shier"], "13.2 13.7 21.2": ["icesheet"], "9.1 6.7 6.0": ["haitian"], "6.0 -2.9 -4.7": ["thebank"], "0.7 -8.5 14.8": ["aes"], "9.7 15.5 10.8": ["geekness"], "13.3 0.3 12.6": ["expeditors"], "6.1 14.7 8.5": ["backstopper"], "23.6 17.5 15.3": ["belcher"], "-1.4 0.3 -2.3": ["bananafancy"], "4.5 3.0 22.3": ["johnston"], "3.8 14.9 12.6": ["bejebees"], "8.1 18.7 23.2": ["hucks"], "16.7 9.0 4.6": ["vx"], "13.2 16.7 6.8": ["plasmasphere"], "-6.1 6.3 10.9": ["neha"], "16.3 6.4 28.5": ["delicous"], "9.7 11.3 10.8": ["lookism"], "-1.0 0.7 8.7": ["darshans"], "6.2 21.1 6.8": ["reenergizes"], "-5.1 25.8 0.0": ["interogation"], "8.8 12.1 14.0": ["merozoites"], "-3.4 7.7 10.1": ["bedspace"], "9.8 3.4 14.8": ["ripely"], "15.4 6.4 15.3": ["decants"], "13.6 7.4 0.8": ["sceme"], "12.7 8.8 21.2": ["hazers"], "11.9 15.8 16.3": ["merriness"], "10.9 11.1 12.6": ["slapfest"], "1.5 16.9 3.4": ["kapos"], "2.2 9.5 14.0": ["condi"], "23.6 18.9 9.0": ["screenful"], "5.7 5.5 3.6": ["parkinsonian"], "22.5 8.3 17.6": ["kitset"], "24.3 22.0 10.4": ["titantic"], "17.0 20.5 22.1": ["droolers"], "15.2 12.5 0.1": ["ferdiei"], "2.8 10.9 21.4": ["gardners"], "21.6 7.2 11.7": ["rockclimbing"], "16.7 9.6 20.6": ["transplanter"], "7.9 2.3 37.0": ["muffulettas"], "9.8 6.7 9.9": ["celli"], "1.3 10.2 2.1": ["foget"], "13.0 15.1 15.3": ["pantie"], "11.9 17.7 6.3": ["ateam"], "7.3 4.5 4.8": ["atest"], "-0.3 -10.5 6.6": ["aquarobics"], "15.9 19.5 13.7": ["harpie"], "9.9 4.2 13.0": ["skived"], "3.9 13.6 10.2": ["maladjustments"], "14.4 6.4 7.0": ["chirruped"], "4.1 17.3 16.1": ["sensless"], "-6.6 12.1 -10.1": ["argueing"], "17.8 7.9 20.8": ["swillers"], "7.7 13.8 -0.5": ["localizable"], "-0.3 13.1 8.1": ["dataplane"], "5.3 6.2 20.3": ["anamensis"], "5.9 26.2 4.1": ["distroyed"], "16.3 17.3 9.9": ["everest"], "11.5 5.5 13.8": ["overcapitalised"], "11.1 5.5 5.2": ["thefederal"], "0.0 -6.6 11.3": ["nagpa"], "2.6 1.4 13.1": ["tetrathlon"], "-0.2 5.8 -2.0": ["ially"], "-2.8 3.4 12.1": ["zonulin"], "0.2 11.2 11.9": ["iwe"], "20.7 11.5 25.8": ["canas"], "14.1 2.7 7.2": ["moob"], "19.0 8.1 17.7": ["stimulas"], "-1.8 5.7 17.8": ["topweights"], "-5.5 5.1 1.2": ["poststroke"], "26.2 4.6 46.0": ["garoupa"], "9.1 14.6 11.5": ["repellently"], "9.3 12.3 11.3": ["cariocas"], "7.1 11.9 5.0": ["inator"], "14.7 6.9 19.1": ["ghagras"], "-0.2 5.1 11.0": ["lacross"], "-3.5 16.0 0.9": ["officialize"], "-5.2 8.0 4.4": ["institutionalist"], "17.8 -1.9 31.0": ["friers"], "18.4 0.2 6.6": ["nanocomponents"], "5.6 -4.8 10.8": ["biyearly"], "20.0 -9.8 11.5": ["pouffe"], "11.5 10.0 29.2": ["giganteum"], "5.0 7.6 11.5": ["dega"], "2.2 3.7 7.4": ["guaiac"], "12.3 9.9 15.4": ["succah"], "11.4 10.8 15.6": ["rollergirl"], "1.2 1.3 2.5": ["immunogenetics"], "0.7 14.8 4.6": ["storng"], "-0.6 0.5 11.6": ["kisi"], "-1.8 4.5 27.1": ["trebbiano"], "4.4 27.0 6.6": ["discomfits"], "8.1 6.2 8.5": ["deskilled"], "16.7 19.2 32.7": ["tommies"], "17.7 20.7 23.5": ["griffons"], "-7.2 4.2 5.4": ["misfiling"], "5.3 -1.0 2.8": ["antibribery"], "1.7 9.9 10.8": ["overcalled"], "3.8 15.7 7.5": ["potentia"], "5.7 -2.8 3.3": ["andrelated"], "9.7 4.2 19.0": ["prostanoids"], "10.3 4.2 16.6": ["pongamia"], "11.5 3.1 13.4": ["sheafs"], "12.0 18.7 -4.4": ["stragegy"], "11.5 6.7 9.1": ["wach"], "9.7 5.8 8.1": ["pelletisation"], "3.3 17.8 11.1": ["comedones"], "1.4 3.9 15.4": ["gayee"], "18.7 20.9 26.8": ["bowlines"], "1.1 8.0 17.8": ["cheq"], "14.4 15.8 34.1": ["jugging"], "19.7 -6.1 0.5": ["acquisitons"], "1.2 13.5 18.5": ["bandha"], "15.6 0.8 -4.5": ["floorcare"], "10.9 7.3 2.5": ["trafficks"], "15.7 12.1 30.1": ["teasel"], "0.4 -1.2 21.5": ["tannat"], "7.8 14.2 12.0": ["villiage"], "11.3 4.2 7.0": ["connnection"], "7.7 8.6 9.3": ["jewellary"], "9.9 12.9 3.1": ["ultraprecise"], "13.7 7.3 30.5": ["piecrusts"], "15.3 3.7 29.0": ["mola"], "4.7 17.8 3.7": ["bribable"], "15.9 3.0 31.2": ["palmful"], "4.0 4.2 13.4": ["tena"], "14.8 1.6 15.6": ["fitty"], "5.5 19.0 6.3": ["markos"], "1.5 -2.2 6.9": ["lucknow"], "-5.7 4.8 -0.4": ["afferents"], "-4.4 2.0 2.8": ["crystalloid"], "9.8 20.3 17.8": ["overstriding"], "4.6 12.1 14.3": ["nanorings"], "2.6 -3.6 9.1": ["transoral"], "1.3 19.0 10.7": ["fueds"], "7.7 26.3 3.4": ["temporized"], "25.3 11.1 20.4": ["luges"], "-0.1 10.7 2.9": ["substantiative"], "14.1 9.3 23.1": ["gangline"], "7.1 21.5 12.5": ["distrupt"], "5.4 8.7 8.8": ["lfc"], "-4.5 5.5 5.9": ["deacetylation"], "-0.3 12.8 0.8": ["mitogenic"], "0.1 8.4 14.7": ["evert"], "9.2 12.0 13.9": ["franticness"], "-0.3 8.4 11.3": ["redefaults"], "-2.2 11.1 5.4": ["subsoils"], "10.0 11.6 5.0": ["zef"], "5.4 7.0 7.6": ["ralley"], "9.4 2.4 5.0": ["eigen"], "14.8 23.5 11.2": ["ditherers"], "8.6 14.3 4.8": ["diacritics"], "11.0 25.4 12.7": ["disintegrations"], "-0.1 20.5 17.7": ["definently"], "15.7 -0.7 -8.7": ["parnership"], "8.6 -3.6 12.5": ["manda"], "7.3 10.9 23.2": ["gulet"], "18.5 8.4 24.5": ["lathed"], "18.7 8.3 27.4": ["tuffet"], "10.0 17.0 10.1": ["swearer"], "4.2 9.1 34.7": ["dowitchers"], "7.5 2.6 43.1": ["unfished"], "14.1 10.1 19.9": ["achoo"], "3.1 9.2 6.9": ["anycase"], "-1.4 0.3 6.8": ["perfromances"], "-4.4 17.4 -4.4": ["fraternised"], "7.4 5.3 6.5": ["cresol"], "7.2 -6.4 6.1": ["thismorning"], "-6.3 9.8 9.9": ["deduped"], "2.6 16.6 7.1": ["rabblerousing"], "1.3 -3.3 5.8": ["semistaged"], "3.7 16.1 11.9": ["actinomycetes"], "2.2 6.1 9.0": ["drainable"], "-3.7 7.5 9.8": ["drainfields"], "-7.9 13.9 4.9": ["policyowner"], "1.8 1.0 18.4": ["exonuclease"], "5.4 21.4 17.4": ["backchecker"], "15.7 5.8 19.2": ["halfsies"], "12.5 17.2 13.3": ["beaurocrats"], "8.4 9.9 8.3": ["streetsmart"], "2.9 3.5 5.9": ["hwt"], "4.1 11.3 10.7": ["femininely"], "17.6 6.4 12.6": ["mimsy"], "7.8 9.3 22.5": ["seawalk"], "21.8 3.8 16.6": ["fingerboards"], "7.8 3.8 27.0": ["acar"], "9.9 10.5 6.7": ["dalals"], "1.4 11.9 -3.5": ["individualising"], "9.2 7.7 42.3": ["chowda"], "9.7 11.1 15.6": ["digestable"], "16.8 16.6 15.1": ["blurrily"], "1.5 3.7 11.7": ["sapagkat"], "2.1 1.2 15.7": ["fydd"], "9.9 14.7 16.3": ["bawdiest"], "1.3 14.6 19.3": ["lygus"], "4.7 5.0 -1.4": ["querries"], "0.3 8.2 11.0": ["intergenic"], "18.3 5.1 49.5": ["talapia"], "-0.9 9.9 8.8": ["tristesse"], "5.5 14.6 8.5": ["almajiri"], "6.9 7.2 -3.6": ["reportd"], "0.2 4.3 3.2": ["numeraries"], "-1.3 6.3 12.4": ["rancherias"], "7.3 14.3 8.3": ["retriggered"], "6.2 17.7 10.1": ["arduousness"], "8.2 -1.9 6.6": ["lobolo"], "16.3 17.4 5.9": ["barrackers"], "6.1 12.9 14.7": ["gyal"], "6.3 3.0 5.5": ["newproducts"], "4.8 6.8 13.8": ["jocking"], "6.8 4.0 9.8": ["unremunerated"], "11.6 0.5 10.2": ["electo"], "4.8 3.2 8.1": ["deodorization"], "1.3 10.4 6.1": ["burma"], "2.1 9.4 2.8": ["intelectual"], "6.9 15.9 9.0": ["wordplays"], "14.4 21.2 7.4": ["transhuman"], "13.3 15.1 7.6": ["metacrawler"], "12.7 13.7 8.3": ["ubercop"], "7.9 8.0 14.0": ["shoutfest"], "-1.5 10.5 7.8": ["scrams"], "5.4 20.6 9.8": ["revenuer"], "2.7 2.7 19.3": ["maduro"], "3.9 17.8 10.8": ["amtrak"], "14.5 4.0 25.6": ["delft"], "16.4 6.1 39.7": ["panang"], "-7.2 4.7 -0.7": ["precommitted"], "0.3 -3.6 10.7": ["reapplications"], "23.1 3.7 5.5": ["superluxury"], "8.1 11.6 11.5": ["azimuthal"], "9.7 12.7 4.8": ["delocalization"], "-0.7 6.3 14.4": ["modulo"], "-2.1 1.2 -8.1": ["anopportunity"], "0.8 10.6 18.4": ["bura"], "8.3 5.5 12.6": ["diopside"], "3.1 4.8 4.5": ["nvohk"], "14.1 2.0 24.3": ["torti"], "13.8 4.2 12.9": ["joggle"], "13.2 12.0 11.7": ["kahunas"], "18.3 12.6 10.4": ["cubistic"], "5.8 29.0 3.2": ["worlder"], "3.3 5.2 0.3": ["covenanting"], "9.8 9.8 13.6": ["bharatnatyam"], "0.9 11.7 -4.9": ["witin"], "2.8 -0.6 3.1": ["degre"], "0.5 3.9 11.0": ["gospelly"], "5.5 21.5 -1.4": ["disservices"], "11.9 9.9 10.2": ["cyto"], "-3.5 2.6 0.2": ["nonlosing"], "8.1 0.4 9.5": ["pessaries"], "1.3 17.8 7.5": ["conformably"], "14.1 3.8 32.7": ["claggy"], "18.8 6.4 29.9": ["squill"], "-5.2 -0.1 -5.8": ["irector"], "3.5 9.3 6.4": ["flavopiridol"], "5.0 9.1 -1.3": ["derecognize"], "6.7 11.5 3.7": ["takle"], "-0.5 4.1 17.1": ["gingiva"], "-2.5 24.0 2.9": ["ansar"], "-1.2 -0.0 -2.3": ["cardiomegaly"], "22.3 11.4 22.1": ["poochie"], "16.8 6.3 16.8": ["coverers"], "-4.9 8.8 -0.0": ["nonchurch"], "1.3 20.4 11.4": ["pauperism"], "-9.6 9.9 3.3": ["chp"], "-4.2 6.0 -6.2": ["ssion"], "-1.0 6.1 13.6": ["inscripted"], "0.0 4.8 23.8": ["pumpback"], "9.9 -2.3 10.2": ["mboed"], "-2.5 5.3 18.1": ["nonbudget"], "9.9 4.6 12.7": ["floorplate"], "6.2 5.6 5.8": ["sulfone"], "7.0 6.7 -1.7": ["resuscitators"], "11.5 15.6 26.3": ["brevetoxins"], "7.1 17.5 16.0": ["tontos"], "13.9 9.3 8.2": ["ricket"], "0.7 1.2 9.0": ["nette"], "4.1 1.1 3.2": ["hryvni"], "5.6 -5.6 18.7": ["colostrums"], "13.6 21.9 4.3": ["brazened"], "-3.9 -5.2 -4.8": ["accreditated"], "2.6 15.0 7.6": ["nils"], "3.1 0.8 8.9": ["estab"], "1.9 6.3 1.9": ["amnestic"], "12.4 9.0 9.1": ["valises"], "8.0 19.0 5.5": ["itslef"], "5.5 -4.1 -2.5": ["acccount"], "13.6 0.1 3.5": ["unipoles"], "-4.6 3.2 8.1": ["ostomies"], "12.5 -2.6 23.0": ["enrobing"], "6.6 4.5 17.0": ["kye"], "-0.3 2.8 17.8": ["protien"], "2.7 8.9 10.7": ["artisitic"], "-2.8 -0.5 0.6": ["ury"], "14.4 6.3 17.2": ["sylphlike"], "14.7 2.2 12.3": ["polyhouses"], "8.9 22.3 2.4": ["sanitises"], "11.4 16.2 6.2": ["qr"], "9.7 -1.4 10.8": ["mortgate"], "9.2 -1.0 4.3": ["nofrills"], "8.2 33.3 19.3": ["causeless"], "14.3 0.2 27.4": ["maritima"], "17.1 13.4 17.9": ["doomer"], "4.3 11.8 7.1": ["failsafes"], "3.0 14.7 15.0": ["loused"], "2.2 5.6 6.7": ["procyanidin"], "13.5 8.1 8.5": ["dramatical"], "11.0 11.3 13.2": ["eathquake"], "13.6 18.4 16.3": ["softbox"], "10.1 3.6 14.3": ["canthaxanthin"], "-5.7 -1.0 7.4": ["hsc"], "22.6 2.6 21.4": ["chrs"], "0.3 -0.8 3.1": ["southwestgiftcard"], "0.4 24.8 11.3": ["duelers"], "6.7 6.8 10.8": ["quondam"], "19.8 26.8 20.2": ["landspeeder"], "8.8 18.9 2.5": ["whishing"], "7.3 11.1 14.5": ["defueling"], "-3.6 20.0 13.3": ["snitchin"], "9.1 18.5 16.1": ["shockimpulse"], "4.0 14.9 -4.4": ["wami"], "8.4 15.6 12.2": ["galpals"], "1.1 7.6 10.4": ["conformers"], "16.7 9.1 12.1": ["recto"], "-2.5 9.5 -0.2": ["ublic"], "12.5 6.1 17.8": ["trompe"], "5.0 7.4 10.0": ["filk"], "5.8 24.3 6.2": ["qibla"], "-0.2 -1.7 6.5": ["ninemonth"], "0.2 -1.7 3.1": ["ommunity"], "16.2 10.1 10.4": ["kats"], "2.3 2.8 10.9": ["thed"], "19.5 5.6 3.0": ["splitup"], "11.9 8.2 34.0": ["kittiwake"], "9.8 6.7 37.7": ["backstraps"], "13.4 3.0 17.3": ["craftsy"], "-10.6 13.1 3.8": ["intolerability"], "-5.2 12.9 8.7": ["piriformis"], "6.7 21.0 26.0": ["saltpetre"], "-0.7 -2.0 11.4": ["pbk"], "16.8 20.2 21.9": ["gennakers"], "10.1 7.5 42.0": ["scallopini"], "5.0 11.5 16.6": ["furin"], "8.9 11.6 29.8": ["sambars"], "13.3 18.9 18.0": ["dreamless"], "25.5 11.0 12.6": ["pegasus"], "-1.3 15.0 -0.4": ["holyday"], "7.6 12.8 18.3": ["lungfuls"], "1.4 4.3 17.7": ["worktab"], "15.4 18.5 18.0": ["itchier"], "9.6 12.6 6.1": ["demutualizations"], "10.2 6.5 -0.7": ["batte"], "-3.7 16.0 6.1": ["chlidren"], "3.8 8.3 6.6": ["polaritons"], "-0.9 18.7 5.6": ["verbalising"], "21.2 12.2 11.7": ["streetview"], "8.4 -0.9 1.2": ["europeo"], "7.8 11.0 10.0": ["paddleshift"], "8.3 16.3 10.2": ["hausa"], "10.3 3.6 8.8": ["enscribed"], "11.0 11.9 7.4": ["morts"], "12.2 7.0 20.5": ["africanus"], "9.0 4.9 9.4": ["epilator"], "8.5 4.2 13.7": ["pleasantest"], "3.2 27.4 7.4": ["paleos"], "9.6 -0.8 1.0": ["fulllength"], "11.7 9.4 23.5": ["chlorotic"], "16.4 13.8 7.2": ["assload"], "16.7 13.2 8.1": ["mountian"], "6.9 12.1 11.0": ["untinted"], "-1.9 -0.2 12.0": ["paraffinic"], "7.0 12.2 14.7": ["bacn"], "-3.1 6.7 -0.2": ["probablity"], "10.3 28.3 7.8": ["demiurge"], "11.7 0.6 23.4": ["molas"], "-1.0 12.5 9.8": ["carnotite"], "13.1 6.1 9.0": ["recarpet"], "23.5 26.2 9.4": ["zombiefied"], "12.4 6.7 39.9": ["umeboshi"], "-8.3 6.8 7.3": ["ficer"], "2.4 32.8 1.2": ["reactionaryism"], "2.1 14.4 10.3": ["incovenience"], "3.2 18.3 6.6": ["watever"], "-0.6 5.8 0.7": ["aos"], "15.6 14.6 1.4": ["locaters"], "8.3 5.9 0.7": ["parallely"], "3.7 11.2 1.9": ["topof"], "4.0 -3.2 15.9": ["hsiu"], "27.1 13.0 6.8": ["megastructure"], "12.6 12.3 4.0": ["openned"], "2.9 17.1 19.6": ["crapshoots"], "-3.4 4.4 5.6": ["ergotamine"], "15.1 6.6 9.5": ["autojumble"], "-7.9 7.5 6.0": ["postexposure"], "16.4 4.4 4.5": ["supercard"], "1.8 8.0 9.4": ["bhav"], "-1.1 14.4 3.7": ["gentlelady"], "19.3 12.4 12.1": ["gismos"], "10.0 4.5 27.9": ["agros"], "13.7 -10.1 15.5": ["boxtops"], "3.0 1.5 13.2": ["lina"], "6.2 12.1 10.9": ["blir"], "0.5 10.8 10.7": ["barebow"], "-0.1 16.7 -2.4": ["freethought"], "22.8 6.3 13.4": ["hoofprint"], "13.0 17.3 10.3": ["quadrilogy"], "1.8 10.8 15.7": ["namatay"], "-2.7 11.2 -0.7": ["radiocommunication"], "11.8 9.4 9.6": ["formants"], "17.2 25.1 22.0": ["wolflike"], "22.5 5.6 14.5": ["ikea"], "12.3 3.7 8.2": ["bossanova"], "8.6 -0.4 19.1": ["kidlike"], "3.1 11.2 17.3": ["boyracer"], "2.4 22.6 4.0": ["literalistic"], "5.2 5.4 8.8": ["turismo"], "0.9 25.0 2.0": ["boder"], "18.3 16.2 8.3": ["deadzone"], "10.8 19.3 14.6": ["hilled"], "19.9 5.0 11.6": ["blingin"], "2.2 23.3 1.3": ["allegiant"], "14.1 -5.4 0.9": ["smartgrid"], "10.1 22.3 11.7": ["euphemize"], "1.7 12.6 9.4": ["safa"], "15.6 5.4 13.2": ["recyle"], "17.9 21.4 6.0": ["deceipt"], "-1.5 33.2 -0.4": ["deconflict"], "2.6 2.4 3.9": ["offgas"], "13.1 12.6 12.7": ["brawns"], "5.2 8.6 24.6": ["clamdiggers"], "-1.4 7.5 7.1": ["exeption"], "15.5 6.6 -2.9": ["frontpages"], "5.2 14.5 3.9": ["untarred"], "6.0 3.8 1.2": ["rul"], "22.4 20.3 9.6": ["eads"], "7.9 12.8 1.4": ["deviced"], "-5.6 4.2 -6.8": ["respresented"], "-0.8 8.1 12.0": ["winterisation"], "8.4 8.9 9.9": ["chaupal"], "14.2 1.4 11.6": ["ishares"], "22.8 8.2 19.7": ["bedspring"], "-0.6 11.2 -2.5": ["onference"], "10.8 12.4 17.8": ["arounf"], "8.8 9.5 9.6": ["overreliant"], "11.1 16.5 6.4": ["frackin"], "5.7 14.4 7.1": ["scantest"], "15.8 13.9 11.4": ["itsown"], "6.0 1.6 9.5": ["nwa"], "3.8 12.2 -0.1": ["homosexualism"], "8.4 6.8 30.4": ["socca"], "7.3 4.0 12.4": ["thrifted"], "14.9 9.6 19.6": ["therizinosaur"], "12.7 8.1 9.6": ["smirkingly"], "-2.4 21.2 15.6": ["loyalities"], "1.6 6.3 6.5": ["assumably"], "4.4 1.2 -1.9": ["prescreens"], "3.9 4.4 6.0": ["stato"], "-1.8 8.8 14.2": ["kapwa"], "0.2 9.9 -0.8": ["pancuronium"], "11.2 6.4 8.9": ["instalation"], "2.3 3.3 7.8": ["transobturator"], "6.5 8.6 18.6": ["keyways"], "11.6 1.0 6.5": ["infrastracture"], "11.1 9.1 15.6": ["bifacial"], "-2.8 8.5 16.3": ["belongers"], "10.5 0.2 3.6": ["breweriana"], "0.6 5.9 1.1": ["osteoblastic"], "7.4 8.6 -1.8": ["microbrowser"], "4.4 9.4 8.0": ["methylxanthines"], "8.8 14.0 10.0": ["desertlike"], "10.1 14.6 10.0": ["mayhap"], "7.4 -6.8 6.3": ["nted"], "3.6 15.0 6.0": ["hermitic"], "16.9 1.0 15.3": ["hummin"], "4.2 13.1 8.1": ["yrd"], "9.7 3.0 23.4": ["phos"], "9.8 11.9 4.1": ["fileshare"], "4.9 3.1 16.8": ["misa"], "8.9 7.5 8.1": ["polysexual"], "3.6 0.4 1.5": ["avings"], "11.0 1.6 1.9": ["anindependent"], "2.3 5.9 13.7": ["occure"], "-1.7 2.9 2.6": ["milad"], "-5.2 11.7 6.9": ["shem"], "-1.0 2.7 15.6": ["pinaka"], "1.2 7.9 10.6": ["nitrogenase"], "14.2 15.3 13.5": ["moonquakes"], "6.2 5.2 12.2": ["cannes"], "1.4 3.8 17.8": ["metagenomes"], "1.9 -3.0 6.8": ["limitedto"], "-0.3 -1.0 9.1": ["marimbist"], "3.0 0.7 3.8": ["rendu"], "11.8 5.0 9.4": ["permite"], "3.7 14.7 4.4": ["intellectualised"], "2.7 5.8 12.1": ["edad"], "19.4 18.7 18.4": ["befouls"], "-1.8 12.6 5.5": ["permiting"], "5.3 -4.4 1.4": ["attendents"], "9.1 8.5 15.6": ["gye"], "7.4 3.7 2.6": ["micromirror"], "32.9 14.8 4.5": ["colossuses"], "27.8 0.3 9.2": ["highflyer"], "-1.3 0.9 9.1": ["dul"], "13.6 10.7 13.2": ["gussies"], "0.2 8.0 4.9": ["mistitled"], "4.4 4.3 17.3": ["carignane"], "13.3 3.0 27.5": ["siamese"], "19.7 4.0 14.4": ["preso"], "1.8 8.0 -0.3": ["antipornography"], "10.6 6.6 7.2": ["phe"], "-1.2 23.6 10.9": ["heretically"], "-1.3 2.1 3.3": ["lling"], "15.2 9.3 9.6": ["bigotgate"], "19.8 14.4 18.4": ["dodgem"], "6.9 9.1 13.2": ["sermonic"], "2.5 6.4 2.4": ["edison"], "-0.8 7.3 6.4": ["neuroimmunology"], "17.7 9.5 -0.9": ["uncloaks"], "14.3 3.0 17.9": ["corers"], "10.7 10.3 10.1": ["transparant"], "3.9 4.4 20.4": ["dessin"], "-9.3 3.0 0.6": ["ented"], "-4.2 11.4 7.4": ["hono"], "5.1 10.7 11.8": ["waria"], "3.3 5.1 -3.4": ["indigeneous"], "0.9 -5.5 7.2": ["fouryears"], "2.4 0.8 18.1": ["sadya"], "-5.0 1.7 4.3": ["sulodexide"], "16.7 12.5 29.7": ["nymphal"], "10.2 1.7 13.0": ["roomette"], "0.7 4.8 4.9": ["inheritability"], "1.6 16.7 -3.1": ["theofficial"], "6.9 -3.4 -2.2": ["wsg"], "17.9 7.5 9.0": ["totaliser"], "-1.0 3.5 10.9": ["gusta"], "-2.1 6.9 12.9": ["chalega"], "12.5 7.3 9.5": ["zehn"], "17.1 14.9 6.5": ["pedastal"], "8.2 4.2 32.2": ["benthos"], "11.3 15.5 8.6": ["posterize"], "11.2 6.2 20.1": ["trapezium"], "7.1 1.9 13.1": ["seguro"], "7.5 20.8 15.2": ["miedo"], "7.8 12.9 8.2": ["ballsed"], "8.4 9.5 18.3": ["reciprocals"], "5.7 8.9 6.8": ["cibi"], "14.4 8.7 11.4": ["justinbieber"], "20.7 3.7 14.8": ["babassu"], "7.6 5.9 6.1": ["nondestructively"], "7.1 6.8 28.3": ["rhubarbs"], "21.2 6.9 14.4": ["aswirl"], "5.9 8.9 17.5": ["skiddish"], "16.4 10.5 1.2": ["interantional"], "1.8 7.1 15.1": ["declogging"], "9.1 8.9 10.7": ["picocurie"], "11.1 32.2 4.3": ["psychotronic"], "2.8 11.8 4.5": ["bringt"], "6.7 10.7 17.4": ["cowmen"], "15.6 5.6 26.6": ["woodenware"], "11.2 16.5 2.7": ["patrimonies"], "13.9 13.8 16.5": ["anty"], "8.1 4.1 19.8": ["dixieland"], "14.4 26.3 4.9": ["inflationistas"], "-0.1 6.9 12.9": ["comtemplating"], "9.0 9.4 10.6": ["litlle"], "-1.1 -7.4 8.6": ["dall"], "14.7 3.1 7.4": ["ringin"], "11.4 1.1 13.5": ["cancellous"], "9.8 0.7 -7.1": ["reqd"], "-0.1 4.5 2.3": ["buglary"], "3.3 11.1 7.7": ["probowl"], "2.4 7.6 8.5": ["yahaan"], "19.1 4.1 26.8": ["unappetizingly"], "8.3 2.6 23.5": ["repackers"], "-2.7 26.4 3.2": ["sunnis"], "12.6 18.2 9.4": ["fuckwits"], "-1.6 -5.6 -1.5": ["botonics"], "7.2 11.8 5.3": ["disatrous"], "1.7 6.2 5.1": ["apelin"], "13.1 12.0 3.0": ["disintermediating"], "14.2 19.0 13.5": ["suspensefully"], "13.0 10.2 17.0": ["boozehounds"], "8.9 -3.1 7.0": ["networkwide"], "4.0 3.0 9.9": ["diethylamide"], "9.6 19.0 16.0": ["irruptions"], "-2.4 2.9 6.1": ["accommodators"], "1.2 2.8 15.2": ["giorni"], "6.3 18.3 7.4": ["advantge"], "3.5 7.0 5.0": ["demonetization"], "8.1 3.9 5.1": ["issueing"], "1.4 3.6 4.8": ["crusied"], "1.6 -3.0 9.2": ["schduled"], "-0.2 -4.5 -1.7": ["hospita"], "-3.1 0.5 5.4": ["septoplasty"], "23.4 1.8 18.7": ["barrells"], "-1.1 10.4 8.6": ["delimits"], "-0.6 12.1 3.9": ["burdon"], "1.3 21.8 6.3": ["bangarang"], "-0.7 9.6 -3.7": ["integrable"], "14.4 10.1 31.7": ["tartines"], "10.0 2.7 10.0": ["harmoniums"], "6.9 -2.4 2.2": ["laidoff"], "8.0 17.2 24.0": ["microfilariae"], "7.5 0.9 2.1": ["portolio"], "8.5 9.4 24.9": ["gulay"], "-1.6 1.5 -0.9": ["farads"], "-4.2 7.4 16.2": ["mevushal"], "8.5 15.2 7.5": ["extortionary"], "29.3 2.2 1.2": ["saleman"], "4.7 1.7 12.3": ["juntos"], "9.2 16.2 18.8": ["bullmastiffs"], "-3.7 9.1 5.8": ["cker"], "-9.1 9.2 5.8": ["tedarus"], "-4.8 6.8 2.8": ["benfotiamine"], "10.5 3.4 18.9": ["parasailed"], "7.9 3.5 26.8": ["nongreasy"], "-1.3 14.9 11.0": ["pentameter"], "6.7 19.0 7.8": ["fleetingness"], "2.5 0.8 22.3": ["linkspan"], "10.1 5.9 18.5": ["rosiness"], "17.4 9.0 15.0": ["microserver"], "4.8 20.4 12.3": ["juggalo"], "13.2 2.2 4.0": ["vising"], "15.4 14.6 25.6": ["effeminately"], "7.7 16.8 20.2": ["juglone"], "3.3 5.2 3.2": ["ultrastructure"], "7.0 3.5 8.8": ["ojos"], "6.2 14.9 16.6": ["hopheads"], "-0.9 7.1 1.6": ["contextualises"], "7.5 1.4 25.2": ["grappas"], "9.6 34.5 2.1": ["counteroffensives"], "21.0 3.6 8.6": ["nanobodies"], "5.5 8.3 16.2": ["servin", "ensayo"], "23.2 13.8 27.0": ["bambi"], "-0.7 27.2 6.8": ["intentially"], "3.8 5.6 8.1": ["scratchier"], "18.4 2.9 17.8": ["daiko"], "4.0 8.7 12.1": ["charlton"], "-7.8 10.2 5.5": ["quesitons"], "6.9 2.4 12.1": ["moralers"], "13.3 11.1 29.1": ["wienies"], "-4.4 13.0 5.3": ["unhandled"], "0.6 5.1 8.7": ["asc"], "14.7 12.2 9.3": ["nudey"], "1.3 12.0 -0.5": ["adjudges"], "2.8 1.8 19.1": ["lyophilisation"], "5.4 0.3 7.4": ["millionand"], "6.0 9.7 10.3": ["lete"], "3.9 12.6 20.0": ["suburbanizing"], "-3.8 3.3 7.5": ["parathion"], "-0.2 -1.7 7.3": ["umped"], "11.6 1.7 9.0": ["becau"], "9.5 3.6 30.1": ["winterfest"], "16.5 20.2 1.1": ["uninvented"], "3.2 9.5 16.8": ["riseballs"], "7.9 11.8 21.0": ["floriculturists"], "-1.1 8.5 6.7": ["bondings"], "15.0 14.2 9.9": ["horrormeister"], "6.9 11.5 33.5": ["sangrita"], "12.7 12.8 -0.5": ["serice"], "9.8 6.5 24.5": ["buka"], "11.4 12.5 2.4": ["srong"], "4.9 -8.4 -8.7": ["conjuntion"], "5.9 4.1 17.2": ["synteny"], "0.3 8.6 4.3": ["nonaccidental"], "6.5 8.9 11.0": ["asean"], "9.5 2.7 8.5": ["puesto"], "11.5 12.3 15.6": ["onomatopoetic"], "-0.7 11.9 7.3": ["isha"], "14.0 20.1 5.2": ["waylays"], "13.7 28.3 13.8": ["scoffer"], "9.6 8.0 17.5": ["hantaviruses"], "4.8 1.2 21.2": ["feedgrains"], "6.2 21.9 13.9": ["myslef"], "2.4 -1.5 7.8": ["trainor"], "14.9 6.6 20.9": ["oxcarts"], "2.2 21.0 5.4": ["misconceive"], "5.1 8.2 6.7": ["sidefoots"], "-0.7 10.4 7.6": ["adenomyosis"], "14.8 17.6 12.3": ["muscleheads"], "14.2 0.1 12.8": ["flotels"], "4.9 9.0 13.4": ["antiobiotics"], "1.7 12.7 6.4": ["anywere"], "20.0 9.8 18.6": ["carboniferous"], "6.5 -5.1 5.2": ["scriptless"], "19.6 17.5 24.2": ["protoplasmic"], "14.1 5.3 12.1": ["resiting"], "8.9 -1.9 33.2": ["dolmathes"], "-1.2 -5.5 4.8": ["desogestrel"], "10.6 5.9 -4.7": ["reponds"], "20.6 22.5 4.6": ["boobytrap"], "9.6 16.5 12.1": ["forlornness"], "-2.5 6.0 12.0": ["transuranic"], "4.8 10.8 20.3": ["torre"], "10.5 9.4 19.6": ["keratins"], "10.8 -3.3 -1.4": ["liquefier"], "14.4 6.6 29.2": ["tamaracks"], "14.0 1.8 10.3": ["rehomes"], "5.6 1.2 -3.0": ["plm"], "6.3 -4.4 12.5": ["rese"], "23.6 6.1 23.8": ["thonged"], "5.9 -0.4 8.7": ["pme"], "19.7 17.5 20.9": ["flitters"], "20.0 22.8 15.9": ["chthonic"], "20.9 4.1 22.6": ["garniture"], "-2.8 19.6 0.2": ["experiencers"], "3.5 9.2 12.5": ["nadi"], "1.9 3.0 31.6": ["boquerones"], "14.4 3.3 16.8": ["aldrin"], "1.8 -10.5 -10.7": ["proje"], "13.2 25.6 13.4": ["disembowels"], "12.0 4.2 14.5": ["karaokes"], "3.8 7.5 7.9": ["clericals"], "3.6 3.7 5.0": ["outtouched"], "1.2 4.1 1.9": ["freefone"], "2.9 12.3 12.5": ["bakla"], "14.3 1.4 12.6": ["batucada"], "7.8 -0.6 11.4": ["iechyd"], "20.2 22.8 15.2": ["thunking"], "11.4 8.1 8.9": ["autobus"], "7.4 11.6 41.0": ["snaggers"], "10.0 13.5 13.0": ["tremblers"], "3.8 11.5 -2.6": ["tvants"], "1.8 1.3 0.7": ["noneducator"], "17.9 -2.0 -5.4": ["bsed"], "9.0 5.1 10.3": ["dropps"], "3.4 7.4 12.2": ["leucocytes"], "17.6 14.1 8.4": ["tmo"], "0.4 20.9 12.8": ["unmasculine"], "14.7 10.7 27.0": ["palmyra"], "0.8 27.1 4.1": ["judenrein"], "-0.5 3.9 10.7": ["condylar"], "14.6 15.4 17.1": ["barehanding"], "13.9 10.1 23.1": ["provender"], "8.6 10.4 8.9": ["chromakey"], "15.7 7.6 30.6": ["cymbidium"], "8.8 -4.2 35.1": ["marionberries"], "19.3 -3.1 16.3": ["schmancy"], "-1.6 3.3 -10.5": ["asenior"], "1.0 -1.1 20.0": ["vanning"], "9.9 4.9 16.3": ["dzongs"], "7.7 12.6 10.3": ["sportman"], "0.1 1.2 8.7": ["ude"], "8.9 7.3 18.8": ["checkering"], "23.6 5.7 26.4": ["pully"], "-0.8 -0.2 10.3": ["semicustom"], "16.5 2.7 33.6": ["bistec"], "4.2 23.1 5.0": ["pourous"], "0.4 16.1 6.4": ["focally"], "19.3 28.6 10.0": ["superpowerdom"], "14.1 20.7 12.3": ["paralyzingly"], "10.9 1.7 10.3": ["veejays"], "12.9 22.0 14.7": ["brazening"], "15.6 -1.6 28.7": ["winy"], "14.9 10.0 13.8": ["boozily"], "19.7 5.5 11.9": ["billio"], "3.1 5.1 11.7": ["isotopically"], "12.5 2.0 31.6": ["chinquapin"], "15.7 6.0 17.4": ["picturebook"], "-0.2 -0.6 9.5": ["heddlu"], "10.0 12.9 19.0": ["convivially"], "4.4 8.8 5.1": ["refereee"], "-5.3 16.7 2.7": ["sucesses"], "-7.6 9.4 2.6": ["paralytics"], "11.5 9.0 5.1": ["leder"], "17.3 14.0 12.6": ["whol"], "12.3 0.7 5.7": ["geneaology"], "26.9 -1.1 16.0": ["minifridge"], "-1.5 -1.1 3.6": ["ofother"], "20.7 6.7 11.4": ["bine"], "8.0 12.8 13.2": ["touchfinder"], "5.4 12.7 4.1": ["flamewar"], "10.9 9.5 -0.5": ["impassionate"], "-3.5 10.3 2.2": ["impotant"], "9.4 0.1 11.8": ["enthu"], "10.2 18.3 13.2": ["sundowns"], "8.1 10.9 13.8": ["bult"], "14.7 1.1 37.5": ["cotechino"], "7.0 12.0 14.6": ["pasterns"], "8.0 12.2 5.6": ["oficially"], "8.0 11.8 13.2": ["autorikshaw"], "16.3 10.1 15.5": ["drinky"], "6.7 16.5 4.2": ["unguardedly"], "6.1 4.1 2.4": ["apositive"], "8.0 11.9 15.8": ["subaru"], "-0.3 7.4 5.5": ["mgeist"], "13.4 10.5 13.2": ["nanoneedle"], "-1.7 2.9 16.8": ["selenomethionine"], "0.5 4.5 -1.1": ["thoracoscopy"], "12.3 6.8 15.7": ["bizzers"], "9.6 20.4 23.7": ["chital"], "18.9 13.3 9.1": ["developent"], "13.9 6.3 15.1": ["photomicrography"], "13.0 0.1 3.9": ["disponibile"], "20.5 4.0 17.4": ["barkcloth"], "22.3 -3.0 7.4": ["privateequity"], "5.7 3.8 12.4": ["filmlike"], "12.6 8.2 10.7": ["washateria"], "-0.5 12.8 8.5": ["gute"], "7.5 12.7 21.6": ["setu"], "5.8 16.1 3.4": ["fleed"], "5.6 5.1 9.2": ["vagus"], "12.0 0.7 21.0": ["australopithecine"], "7.6 7.1 20.3": ["fleshiness"], "11.9 9.5 13.7": ["frumps"], "-2.6 7.0 6.5": ["emmys"], "-5.1 4.4 7.7": ["consitent"], "1.4 0.4 2.7": ["equipos"], "8.8 8.9 21.2": ["stales"], "10.0 13.3 18.8": ["bestower"], "24.0 14.1 23.4": ["copal"], "14.2 15.7 16.6": ["poulation"], "16.4 16.3 20.9": ["woodman"], "18.6 12.7 25.0": ["unmanicured"], "8.3 4.4 14.1": ["teel"], "17.3 -0.2 8.9": ["unbundles"], "1.2 -1.5 12.4": ["paleoecologist"], "4.7 8.4 1.4": ["mailserver"], "-3.1 -1.9 -2.1": ["negatived"], "1.2 3.3 11.8": ["biobehavioral"], "9.2 0.2 4.1": ["commmission"], "2.3 6.8 1.4": ["orthomolecular"], "2.3 14.1 0.7": ["skepticisms"], "16.1 4.4 10.9": ["measely"], "4.3 19.2 7.4": ["concomitants"], "2.4 10.6 5.4": ["snailmail"], "-0.9 5.7 9.0": ["nonimpact"], "1.6 7.6 10.7": ["bidoon"], "8.7 6.6 26.2": ["elands"], "7.6 3.3 21.0": ["ophiolite"], "-6.9 1.3 7.9": ["jede"], "10.7 11.2 18.3": ["smackin"], "16.6 15.2 2.6": ["silvertail"], "5.8 18.7 25.0": ["okro"], "20.1 7.7 15.0": ["lightshows"], "9.9 3.2 1.0": ["ngi"], "9.8 2.5 3.3": ["microdevice"], "5.8 22.3 5.1": ["despotically"], "11.1 3.1 21.9": ["robusto"], "-2.2 2.8 1.0": ["surve"], "3.6 9.2 11.5": ["berberine"], "7.7 15.0 15.1": ["glady"], "18.3 17.9 9.2": ["demonstraters"], "7.2 20.8 22.8": ["lustiness"], "16.5 1.8 21.5": ["bonebed"], "-2.2 12.8 13.7": ["gna"], "11.9 -2.8 2.4": ["clearning"], "4.9 -11.1 6.9": ["atheltes"], "0.3 21.7 2.4": ["farseeing"], "20.1 1.0 16.7": ["refloats"], "9.9 12.9 18.7": ["unprimed"], "9.0 2.0 10.6": ["rox"], "12.8 7.5 12.4": ["cumshot"], "7.1 5.8 -1.6": ["restructuration"], "10.0 7.2 25.7": ["sportfisher"], "-0.5 2.3 6.3": ["homopolymers"], "6.1 15.3 5.4": ["pretargeting"], "2.1 10.6 -6.9": ["maintian"], "-5.5 3.7 6.5": ["rehirings"], "9.5 14.9 5.4": ["fastchat"], "-2.6 8.6 7.9": ["recombinase"], "20.7 25.3 25.4": ["ratlike"], "14.7 8.4 12.6": ["slowcoach"], "15.0 5.3 3.4": ["intenet"], "18.6 20.1 15.8": ["hokie"], "8.3 -2.4 9.2": ["nich"], "2.8 7.6 -2.0": ["timebeing"], "-6.7 8.4 2.2": ["purviews"], "19.0 18.0 6.6": ["hatchetman"], "15.8 22.2 20.7": ["hilts"], "17.1 6.7 2.9": ["reachs"], "20.4 24.2 -2.8": ["optronic"], "12.6 1.1 27.1": ["skimboards"], "8.9 13.9 9.0": ["ablility"], "7.5 -1.1 18.4": ["matta"], "13.6 10.7 20.4": ["rapido"], "3.4 7.5 7.5": ["fosterer"], "12.4 51.0 20.1": ["enemys"], "3.9 5.0 7.6": ["watercut"], "5.4 3.6 30.6": ["rava"], "3.0 12.2 8.6": ["vicky"], "2.5 6.3 0.3": ["seminfinal"], "-3.0 3.9 8.2": ["thioridazine"], "10.7 19.8 14.0": ["poilus"], "2.2 7.0 19.4": ["tonu"], "16.2 10.7 16.6": ["gappy"], "0.2 -2.1 6.9": ["novelettes"], "2.6 11.0 20.3": ["overexercising"], "16.4 18.4 27.1": ["cowabunga"], "2.5 0.4 11.0": ["heller"], "5.2 3.1 0.1": ["termsof"], "-2.0 10.9 6.3": ["bloodborne"], "4.2 0.6 1.1": ["rotatory"], "15.1 8.0 -0.2": ["copywritten"], "0.4 -1.5 2.6": ["nineyear"], "4.1 -2.5 10.6": ["prounounced"], "8.6 9.1 19.8": ["eyedroppers"], "0.0 10.5 8.7": ["leav"], "1.9 12.9 10.2": ["permissively"], "10.9 0.6 -0.4": ["reache"], "-4.4 1.7 3.2": ["audiotaping"], "-0.3 5.7 -1.8": ["ammassed"], "-1.2 8.8 14.0": ["taishang"], "0.9 10.3 10.6": ["outlap"], "11.6 3.9 16.3": ["stressless"], "4.1 13.0 35.5": ["bluewings"], "11.1 5.7 14.5": ["spreadbetters"], "-0.1 14.0 -4.5": ["misued"], "5.7 -1.5 7.1": ["extrapyramidal"], "18.8 22.5 12.6": ["minifigs"], "0.7 11.2 9.0": ["maaf"], "5.7 25.8 7.6": ["spiritualize"], "11.3 18.3 15.3": ["hoosiers"], "-1.7 5.3 2.3": ["respectivly"], "1.3 30.6 2.5": ["clandestinity"], "19.6 13.2 15.3": ["mudpit"], "18.6 2.9 5.3": ["vzw"], "2.8 4.5 4.4": ["fanshot"], "23.1 15.2 28.3": ["fluffball"], "1.8 4.6 -1.7": ["geocodes"], "11.9 12.8 12.5": ["strappings"], "20.8 10.7 10.9": ["nonremovable"], "10.6 -3.9 9.6": ["allmediascotland"], "1.8 8.0 0.2": ["parametrics"], "15.6 27.7 38.9": ["lubbers"], "10.3 21.6 7.4": ["reinvaded"], "7.4 40.2 3.3": ["undeterrable"], "13.8 11.7 7.6": ["abuot"], "8.5 -0.5 19.5": ["kinnows"], "4.7 21.4 10.1": ["strenuousness"], "-0.6 -7.0 4.7": ["discplinary"], "2.5 9.3 13.0": ["zoner"], "2.9 -0.0 -3.8": ["microforms"], "18.1 -2.1 29.3": ["poppadums"], "12.9 27.0 7.2": ["dastard"], "3.9 28.7 3.1": ["intrepidness"], "7.0 14.5 16.1": ["mswolfestock"], "9.0 15.5 14.7": ["hardily"], "6.7 8.2 4.3": ["psychometry"], "10.6 5.4 29.7": ["mozz"], "2.6 10.6 0.5": ["emt"], "0.5 5.5 28.3": ["asam"], "6.6 11.3 4.0": ["menas"], "14.9 0.4 17.7": ["mehandi"], "13.5 19.2 47.8": ["chummers"], "0.6 11.7 8.1": ["microstamp"], "1.8 -1.3 7.1": ["sulle"], "3.5 10.2 9.7": ["intensifiers"], "4.4 12.1 23.5": ["penninsula"], "3.2 24.3 4.6": ["kashmiris"], "8.5 30.2 11.9": ["tryto"], "2.0 13.6 12.6": ["unh"], "3.1 12.4 5.1": ["fnd"], "-3.3 11.8 8.6": ["mino"], "11.0 10.3 8.7": ["fingerpost"], "14.6 15.6 17.1": ["mindblowingly"], "1.3 28.3 4.0": ["dalams"], "-2.7 -0.9 -3.7": ["olny"], "6.5 15.0 10.8": ["underconsumption"], "3.6 14.1 17.4": ["lew"], "14.0 21.5 21.0": ["suface"], "6.3 8.8 9.8": ["couchette"], "4.2 10.6 11.6": ["quantize"], "3.1 3.6 3.4": ["gaines"], "0.5 3.8 8.2": ["vicariates"], "-1.4 8.8 13.1": ["amoebiasis"], "5.0 1.0 14.0": ["seet"], "0.5 9.7 5.6": ["ardfheis"], "7.9 -3.6 12.3": ["slipcased"], "7.7 11.9 11.4": ["littel"], "11.5 5.2 22.9": ["chantey"], "-1.5 9.0 -3.1": ["daaras"], "6.5 17.9 6.7": ["handbagging"], "15.2 11.6 6.4": ["legisation"], "12.6 13.2 4.9": ["accusatorial"], "0.1 3.5 -1.9": ["lj"], "7.9 10.8 28.8": ["tuyo"], "24.6 17.8 20.7": ["thwap"], "-6.5 4.5 8.1": ["timebase"], "7.2 0.3 7.3": ["careworker"], "3.4 4.2 15.2": ["peignoir"], "-0.2 13.4 10.0": ["sistren"], "14.3 19.4 3.8": ["toadie"], "4.4 10.2 1.5": ["actos"], "4.0 22.5 -0.4": ["reformable"], "13.6 9.1 15.6": ["kantele"], "3.7 -1.7 19.7": ["milano"], "7.4 8.4 7.8": ["paleoecology"], "-1.8 0.4 1.2": ["tment"], "-4.3 7.7 -1.2": ["sahayaks"], "1.3 19.6 17.7": ["selfing"], "5.4 4.7 13.8": ["cigarrettes"], "11.0 11.8 18.7": ["primered"], "8.6 1.0 -1.2": ["indicatively"], "13.7 6.3 6.1": ["micromechanics"], "2.9 14.7 5.5": ["isit"], "11.2 25.4 15.9": ["hidin"], "-2.2 -1.1 3.7": ["medroxyprogesterone"], "6.8 -0.7 8.6": ["summ"], "3.4 3.5 4.4": ["uspet"], "7.4 12.2 13.8": ["kelmon"], "9.3 1.5 6.6": ["erwartet"], "2.9 5.7 33.3": ["kibbee"], "1.5 17.3 33.5": ["spearfisherman"], "0.8 5.3 1.9": ["midkine"], "5.5 1.2 9.5": ["ninemonths"], "4.3 17.4 12.3": ["condit"], "7.5 18.4 20.9": ["livlihoods"], "9.0 18.5 13.6": ["blackfella"], "-1.8 9.1 13.6": ["combe"], "3.7 9.9 15.4": ["uranophane"], "6.3 16.1 7.2": ["dicate"], "7.3 20.5 10.2": ["bothe"], "4.6 9.5 8.6": ["cattier"], "3.5 5.5 17.4": ["judgings"], "-0.8 2.1 2.1": ["gynaecologic"], "3.5 4.3 10.3": ["weathertightness"], "-0.5 9.4 10.3": ["lowpass"], "24.9 15.2 11.1": ["wavin"], "15.4 9.5 45.1": ["corbina"], "4.0 1.8 5.8": ["formfactor"], "23.4 9.8 13.7": ["nerddom"], "12.1 9.0 12.8": ["yueng"], "24.2 12.6 23.8": ["ovipositor"], "9.6 8.3 8.3": ["parellel"], "1.7 8.8 8.0": ["peptic"], "9.5 4.7 13.2": ["commerative"], "7.9 23.9 3.3": ["totalising"], "5.3 7.9 1.7": ["erscheinen"], "10.0 0.8 2.7": ["halfshafts"], "24.3 -3.0 7.3": ["candlemaker"], "2.3 18.9 3.8": ["noetic"], "4.9 14.2 7.7": ["becausethe"], "8.4 3.9 9.0": ["detta"], "11.3 7.1 15.4": ["asphaltenes"], "7.0 9.6 6.5": ["internetwork"], "7.2 8.9 17.6": ["mercer"], "16.8 20.6 29.5": ["webworm"], "12.9 3.8 19.1": ["lepidopterists"], "9.3 6.4 18.6": ["acrylamides"], "16.7 7.0 14.8": ["mewed"], "8.1 13.1 13.0": ["bhagwan"], "11.8 6.1 14.5": ["polytonal"], "18.5 -5.1 3.5": ["highe"], "13.7 2.4 1.2": ["polevault"], "6.9 1.4 30.2": ["mero"], "-6.2 7.9 5.5": ["factthat"], "9.1 2.9 19.6": ["pasteurizes"], "12.2 3.6 6.2": ["aplusk"], "11.6 0.9 12.0": ["illbruck"], "3.3 9.7 -1.2": ["disapplied"], "0.4 1.8 6.2": ["dapivirine"], "12.7 13.3 20.5": ["burnet"], "12.2 11.7 20.2": ["culo"], "10.1 21.6 14.2": ["extremeties"], "4.6 -0.4 10.7": ["waite"], "7.1 7.6 18.7": ["abouta"], "11.5 4.2 -2.6": ["entitities"], "11.1 0.6 28.6": ["brittles"], "-4.5 1.4 14.9": ["ception"], "8.8 -3.4 -1.0": ["imc"], "14.8 11.4 22.9": ["zappy"], "7.6 6.1 1.9": ["remunerates"], "-7.2 -4.8 -0.4": ["accredidation"], "16.7 1.9 9.3": ["pipemakers"], "9.2 7.4 9.8": ["pipettors"], "24.6 3.7 3.4": ["indusry"], "4.6 18.1 12.1": ["peskiness"], "14.4 10.7 16.4": ["supersuits"], "-1.8 5.5 19.7": ["prepackaging"], "5.2 4.0 11.7": ["chea"], "13.8 13.6 14.3": ["webheads"], "10.3 8.7 13.5": ["nanocars"], "16.6 1.7 -2.3": ["quartely"], "7.1 16.8 11.6": ["decendents"], "7.8 35.4 4.0": ["immobilism"], "18.2 6.7 10.0": ["fabbing"], "5.9 6.8 10.7": ["metocean"], "14.7 12.1 6.6": ["technium"], "9.1 11.2 7.5": ["iconographers"], "5.6 -2.3 33.9": ["zuppa"], "4.8 3.5 -1.9": ["activitist"], "10.3 17.0 28.6": ["coccolithophores"], "-4.3 0.2 8.1": ["ethnomusicologists"], "9.5 5.8 -6.2": ["colourable"], "11.4 4.9 10.8": ["ministorage"], "10.0 -2.8 5.6": ["manufac"], "7.4 7.4 3.2": ["withother"], "8.1 0.3 10.4": ["speciale"], "12.8 11.9 6.3": ["cefquinome"], "1.8 8.9 4.3": ["whr"], "17.3 17.3 36.8": ["planktons"], "1.7 1.4 -2.0": ["beteween"], "5.1 14.4 2.1": ["descibe"], "2.9 2.7 12.5": ["regula"], "8.2 2.5 14.0": ["renee"], "8.9 25.9 11.5": ["youngling"], "2.5 12.6 11.8": ["vibratos"], "19.4 15.8 16.9": ["tasmania"], "20.1 -3.4 2.1": ["precurser"], "11.3 14.3 15.2": ["peepee"], "15.2 -7.2 2.2": ["upstreaming"], "-0.4 -8.8 -8.1": ["hief"], "2.4 23.9 14.3": ["practicer"], "12.3 14.4 14.8": ["luchadors"], "10.5 10.6 16.4": ["hogback"], "12.2 8.7 9.6": ["deadends"], "12.5 -9.3 8.4": ["lifecare"], "1.9 11.0 11.3": ["garib"], "16.4 16.5 10.3": ["musclehead"], "-2.0 7.9 16.1": ["bisan"], "24.0 19.2 25.6": ["timberwolves"], "10.4 8.6 7.9": ["scantier"], "-0.5 19.4 -0.4": ["cryptological"], "22.2 4.3 8.1": ["icesave"], "3.4 20.0 28.3": ["haoles"], "-3.6 10.8 6.4": ["haftarah"], "6.9 11.3 5.9": ["functionable"], "10.3 3.7 7.3": ["partage"], "1.4 -4.3 1.5": ["decisio"], "-2.9 10.0 6.3": ["manometry"], "25.6 11.1 10.0": ["threedimensional"], "7.9 2.0 18.6": ["weekendlong"], "19.8 20.9 12.3": ["overpressurized"], "14.8 2.9 11.0": ["bicyles"], "-1.2 11.5 -5.0": ["sadhaks"], "16.1 0.0 6.0": ["ursodiol"], "2.3 15.8 7.5": ["largly"], "-2.7 5.8 2.4": ["clitoridectomy"], "2.7 5.7 5.0": ["neointimal"], "1.4 -1.0 24.9": ["spr"], "-0.2 12.0 13.4": ["straightman"], "14.0 3.3 16.9": ["kompang"], "8.7 15.9 20.8": ["purpling"], "1.1 15.0 6.0": ["camorra"], "18.3 14.3 7.6": ["flimflammery"], "6.7 19.3 11.4": ["forcasters"], "20.8 5.8 18.9": ["unpopped"], "9.8 -1.8 8.0": ["estrella"], "9.6 10.1 12.1": ["nonintuitive"], "1.5 11.3 12.4": ["eduardo"], "2.8 11.8 15.3": ["greetin"], "7.8 6.1 7.3": ["adalah"], "6.8 20.3 11.0": ["roguishness"], "2.3 17.7 12.3": ["spendaholics"], "14.8 21.4 14.7": ["cloudscapes"], "8.3 10.7 19.2": ["pareo"], "11.7 2.5 8.1": ["boozefest"], "2.7 8.3 3.4": ["pathogenetic"], "5.7 7.6 12.7": ["iodomethane"], "7.2 8.7 13.1": ["wert"], "3.2 8.8 15.4": ["gach"], "6.0 16.1 15.4": ["treatin"], "-4.0 4.9 2.6": ["partite"], "-1.1 3.4 10.9": ["ganyang"], "8.1 6.6 11.0": ["isolettes"], "6.3 9.6 23.1": ["bubbie"], "-1.1 20.3 1.8": ["gyroplanes"], "10.5 1.5 -1.3": ["incluidng"], "-4.5 12.1 9.5": ["bastos"], "9.5 8.4 28.3": ["onagers"], "-0.2 13.6 -3.6": ["consitute"], "-1.8 -2.3 4.1": ["withh"], "28.0 10.8 15.1": ["tepuis"], "8.7 3.1 -2.6": ["unmailed"], "7.6 42.8 -1.3": ["mojahedin"], "4.3 4.6 11.3": ["cytokinins"], "-1.6 -2.8 -2.9": ["disablities"], "0.0 12.4 10.6": ["amily"], "19.2 1.1 22.5": ["chowmein"], "17.2 10.9 7.9": ["gasmask"], "20.2 9.5 26.1": ["bulbed"], "7.3 14.1 4.2": ["factcheck"], "6.6 3.2 1.5": ["reflectometer"], "-1.2 11.8 8.0": ["ecopsychology"], "21.8 12.2 19.8": ["bunghole"], "8.2 12.7 8.6": ["unlinking"], "6.4 18.9 10.8": ["pluribus"], "5.9 0.6 6.6": ["continuesto"], "4.8 -1.3 3.6": ["disbars"], "13.5 7.7 33.5": ["boatlifts"], "-0.8 -1.7 7.2": ["pretrials"], "15.3 6.1 4.6": ["kant"], "19.9 -6.6 1.9": ["annou"], "12.8 15.4 6.4": ["heheh"], "4.2 -7.0 7.8": ["radiothons"], "6.6 15.7 6.0": ["generosities"], "4.2 7.6 6.6": ["uranyl"], "-2.3 0.8 16.3": ["epiphysis"], "21.9 1.0 29.9": ["ribbonlike"], "14.8 3.0 20.6": ["gambrel"], "12.3 -2.8 4.3": ["nealy"], "-2.6 5.4 7.0": ["endotracheal"], "-1.0 13.8 7.9": ["stiking"], "6.6 10.0 6.1": ["iy"], "12.1 20.6 14.5": ["superluminal"], "7.4 24.1 10.1": ["rudo"], "4.6 7.7 -0.4": ["highroad"], "5.9 3.1 12.1": ["tiful"], "8.6 12.2 10.7": ["chatshows"], "23.7 12.8 19.5": ["cowcatcher"], "5.5 7.3 8.5": ["runfest"], "-7.2 14.0 4.1": ["bsent"], "-0.5 15.8 9.4": ["arenaviruses"], "22.1 5.2 13.7": ["plyboard"], "6.9 4.6 8.1": ["ergosterol"], "9.0 25.5 2.1": ["unloseable"], "8.8 0.6 30.9": ["deseeded"], "9.1 8.2 28.9": ["salter"], "8.4 15.0 21.7": ["bismarck"], "11.6 4.6 10.3": ["unenergetic"], "14.9 8.9 24.5": ["wildwood"], "1.4 -2.9 10.6": ["exta"], "1.6 5.6 7.9": ["lipoxygenase"], "1.8 -0.8 3.7": ["sceond"], "-3.2 9.0 3.9": ["nonischemic"], "25.6 25.2 19.7": ["fleshless"], "1.9 17.7 11.9": ["morganatic"], "6.2 -5.8 3.7": ["bemade"], "5.0 12.5 5.7": ["speedwise"], "-2.1 5.7 5.4": ["necrological"], "12.8 8.5 9.3": ["hydrocephalic"], "-0.4 -1.2 7.9": ["neuropathologic"], "-3.4 2.6 4.2": ["foru"], "19.1 13.3 13.6": ["clickstreams"], "17.9 11.4 7.2": ["ursprache"], "-4.2 -0.8 2.8": ["minonline"], "6.2 20.6 3.6": ["shuold"], "5.6 23.0 1.0": ["theocon"], "0.1 14.3 17.5": ["permitee"], "-2.0 12.2 3.3": ["populares"], "-4.0 5.9 18.9": ["overlimits"], "7.9 22.5 14.9": ["wiccans"], "6.4 15.9 16.2": ["immitation"], "8.6 4.4 17.6": ["machair"], "9.3 8.7 -2.3": ["deficiently"], "-1.2 10.4 3.8": ["autocephalous"], "6.7 12.2 11.3": ["denarii"], "5.8 4.1 4.6": ["noter"], "8.1 1.4 19.0": ["polyunsaturates"], "1.2 6.3 7.0": ["hijo"], "0.6 11.4 5.7": ["avergae"], "7.3 8.6 11.7": ["favorit"], "20.9 -5.2 9.3": ["multibuilding"], "12.0 7.3 22.9": ["agglomerating"], "8.7 1.5 20.5": ["raisons"], "6.4 7.2 3.6": ["deprecatory"], "8.6 6.1 13.8": ["morena"], "-8.4 4.6 2.1": ["vasopressor"], "-7.5 1.9 8.9": ["councilmanic"], "10.8 6.2 2.6": ["courrier"], "8.6 13.8 6.0": ["watergate"], "8.9 12.9 21.0": ["pupation"], "14.6 5.5 16.2": ["aluminosilicate"], "0.1 10.0 15.6": ["hamein"], "18.3 18.0 20.8": ["cowpats"], "7.9 10.1 2.3": ["intergraded"], "9.0 -4.2 23.4": ["niu"], "9.2 4.3 12.5": ["xavier"], "-0.3 -0.6 8.8": ["housewarmings"], "-5.6 4.3 9.9": ["bisacodyl"], "15.2 10.3 15.4": ["jali"], "9.4 5.9 9.5": ["dramz"], "13.2 11.3 -3.8": ["gorup"], "7.4 23.1 5.2": ["fomenters"], "-1.1 29.7 7.0": ["irredentists"], "1.8 10.3 12.4": ["kimi"], "8.2 13.2 12.9": ["fondler"], "5.8 3.1 10.3": ["kort"], "0.0 11.2 4.8": ["prolongations"], "8.9 3.2 13.4": ["frevo"], "17.9 9.3 -0.6": ["anticopying"], "16.2 2.6 22.3": ["bowery"], "22.3 -1.4 10.1": ["uncaps"], "7.6 3.2 10.5": ["pearson"], "11.4 5.1 4.8": ["lits"], "6.4 16.4 6.5": ["peopleand"], "5.7 -3.4 12.9": ["bik"], "-0.4 15.2 -0.4": ["expatiates"], "6.2 25.1 13.1": ["foully"], "5.9 -0.9 6.0": ["phosphoprotein"], "5.5 15.1 13.5": ["stimming"], "7.8 16.2 16.6": ["thum"], "7.0 1.0 9.5": ["lipoplasty"], "11.1 6.0 21.5": ["sisterships"], "11.7 8.7 1.7": ["transducing"], "1.1 10.9 3.6": ["exchage"], "5.3 1.9 -4.1": ["shuting"], "18.3 4.0 28.8": ["millefiori"], "4.4 13.3 16.2": ["dthe"], "0.9 1.3 2.7": ["rry"], "0.7 11.0 19.6": ["bagyo"], "-4.2 -0.8 -0.9": ["treatmentof"], "18.5 28.8 24.3": ["annelid"], "-3.4 -0.6 1.4": ["nonstimulant"], "-1.7 8.4 -7.6": ["attourney"], "8.6 20.6 6.8": ["oppresive"], "-0.3 3.2 11.6": ["roundballers", "inkind"], "12.3 9.2 14.4": ["toreadors"], "7.4 9.6 -4.1": ["skyguide"], "-4.0 5.8 18.2": ["megadrought"], "15.3 3.0 14.5": ["frowsy"], "8.6 11.4 10.9": ["isosceles"], "-1.5 10.2 20.6": ["parda"], "-0.2 5.1 16.8": ["polki"], "6.2 3.3 6.5": ["brithday"], "5.2 -4.7 11.4": ["agricoles"], "0.9 18.9 5.0": ["beltings"], "-0.7 21.3 7.4": ["deracination"], "16.1 6.0 5.0": ["exertainment"], "9.8 3.7 9.9": ["openbsd"], "8.9 11.3 25.8": ["capensis"], "13.0 3.9 4.4": ["webdesign"], "13.2 0.3 8.7": ["minings"], "4.2 -7.3 8.6": ["commerciale"], "-4.2 3.6 1.0": ["ained"], "6.8 17.5 16.6": ["middleground"], "10.9 5.3 16.7": ["roro"], "-4.3 10.3 5.3": ["intraventricular"], "0.9 19.9 17.7": ["lovelessness"], "5.7 7.8 2.9": ["nonappealable"], "10.7 2.8 12.3": ["macerator"], "13.2 7.6 2.0": ["supurb"], "1.5 12.2 10.4": ["identifing"], "0.4 9.4 5.5": ["ronda"], "-7.1 11.2 3.1": ["disinvitation"], "9.6 6.4 8.6": ["gentlefolk"], "-0.6 3.8 2.4": ["acrolinx"], "4.5 21.6 5.1": ["knavish"], "-16.3 0.4 10.5": ["marz"], "12.4 5.5 12.2": ["lunette"], "9.7 9.4 2.9": ["trepanation"], "3.8 15.2 6.3": ["superbowls"], "5.6 -3.8 7.7": ["ouncil"], "3.5 -0.7 5.1": ["exhanges", "interhall"], "1.1 2.2 12.1": ["lessoning"], "13.8 14.2 9.7": ["wornout"], "7.2 22.9 4.1": ["humantarian"], "2.2 20.0 -6.8": ["apposing"], "11.7 14.8 7.7": ["snipings"], "11.2 12.2 15.3": ["resharpening"], "-1.3 4.1 0.4": ["photostable"], "3.6 7.4 17.6": ["nattokinase"], "10.6 13.8 9.3": ["conduces"], "-1.0 2.8 7.2": ["identi"], "17.6 2.2 7.1": ["warehouselike"], "13.1 3.2 18.2": ["slipcases"], "-4.3 13.5 9.1": ["hyperhydrosis"], "6.0 19.0 7.2": ["anny"], "0.1 3.9 -1.9": ["presid"], "10.9 14.4 18.6": ["lezzie"], "1.4 16.1 7.8": ["siasia"], "3.1 3.1 1.7": ["significative"], "14.2 9.5 30.4": ["prunus"], "0.9 0.3 23.2": ["kcals"], "12.2 20.6 10.9": ["sleave"], "9.8 -9.3 -3.3": ["announcedthat"], "-3.0 17.2 8.5": ["individ"], "8.1 10.4 4.4": ["fantasista"], "2.4 11.1 24.7": ["propagules"], "6.9 5.9 10.6": ["sourcebooks"], "-2.6 10.7 -0.8": ["arrhythmogenic"], "8.3 13.7 18.5": ["satras"], "8.3 19.5 8.4": ["mmmkay"], "7.9 11.8 17.2": ["needleworkers"], "18.9 11.0 7.3": ["gogglebox"], "10.2 22.7 11.7": ["mammaglobin"], "10.1 11.4 3.1": ["sactions"], "19.6 19.1 22.4": ["whiplike"], "0.6 15.2 0.8": ["feistily"], "7.3 21.1 23.2": ["submersing"], "2.9 26.2 13.1": ["bellum"], "19.0 11.7 13.2": ["megacap"], "5.1 5.0 11.3": ["columnizing"], "3.0 7.3 6.1": ["editais"], "4.0 6.3 10.0": ["hemos"], "10.0 10.7 15.2": ["riaa"], "22.7 11.0 13.4": ["uplights"], "-3.6 22.7 14.4": ["wantoks"], "11.3 13.7 15.6": ["nrl"], "2.6 14.6 14.3": ["howmuch"], "9.4 14.1 2.5": ["biosignature"], "10.2 15.8 13.1": ["hexagram"], "5.8 5.6 16.7": ["perro"], "1.8 -0.9 19.7": ["korn"], "13.2 3.0 7.9": ["targe"], "-0.3 12.7 1.3": ["ungazetted"], "-1.3 11.2 2.3": ["chassid"], "12.7 10.1 9.3": ["discman"], "14.0 -2.4 0.8": ["technotrans"], "12.5 2.2 6.3": ["funfare"], "1.3 7.9 18.1": ["likay"], "13.2 24.5 19.5": ["carronades"], "11.1 3.3 9.4": ["ressurected"], "0.2 4.0 8.9": ["paraoxonase"], "5.0 -2.2 2.9": ["andperformance"], "6.5 9.9 15.8": ["sufganiot"], "7.4 17.2 12.8": ["gists"], "0.0 -5.4 7.2": ["unjoined"], "3.4 6.4 14.9": ["biominerals"], "8.6 23.2 10.6": ["nonsenses"], "1.7 8.8 9.5": ["chieftainess"], "4.7 -1.1 8.4": ["pedicurists"], "9.0 9.1 4.5": ["pz"], "-4.0 6.1 16.7": ["bhatta"], "18.1 10.9 22.3": ["imperials"], "12.6 4.9 15.2": ["nyama"], "3.6 -5.2 18.6": ["culinology"], "2.3 5.9 2.5": ["upfitters"], "6.4 10.8 5.9": ["electroactive"], "-3.9 0.2 12.1": ["takt"], "2.3 44.0 6.6": ["armys"], "8.2 4.0 1.1": ["lightbars"], "-0.4 8.1 1.9": ["faithbased"], "5.5 12.6 14.1": ["physis"], "15.4 -2.5 22.7": ["handknit"], "11.9 13.5 14.6": ["lapa"], "-0.2 13.7 8.6": ["dystonias"], "-1.6 17.2 6.2": ["mallam"], "-0.2 6.9 1.6": ["tomatometer"], "9.3 5.5 -2.0": ["reup"], "10.2 14.4 8.8": ["ibrahim"], "12.4 11.2 16.9": ["propah"], "16.6 6.7 18.5": ["windcheaters"], "8.9 20.1 -1.4": ["theuse"], "7.5 9.7 8.4": ["plese"], "5.5 10.8 8.4": ["autocompletion"], "7.1 13.6 12.5": ["leucogranite"], "-6.2 5.1 6.8": ["adjunctively"], "0.3 1.9 6.2": ["buted"], "21.7 11.9 23.1": ["octupus"], "16.8 7.9 35.2": ["coconutty"], "6.3 4.6 2.4": ["noncontributory"], "4.6 7.3 1.1": ["newsblog"], "13.3 31.1 6.6": ["frienemy"], "-5.1 9.5 5.7": ["reoccurence"], "7.6 2.1 26.5": ["modak"], "10.4 -0.9 10.3": ["petrography"], "11.9 10.9 9.0": ["swotty"], "20.8 0.9 14.4": ["bodhrans"], "6.9 -6.0 2.2": ["annualreport"], "0.6 6.9 -1.4": ["subservicer"], "4.0 -3.1 8.4": ["modd"], "13.1 6.5 21.3": ["sprayfields"], "5.0 1.5 4.5": ["resculpting"], "9.5 7.0 12.0": ["accupressure"], "12.4 0.8 10.8": ["fincas"], "16.2 11.1 0.2": ["postapartheid"], "23.8 9.0 32.5": ["hawser"], "17.3 20.0 15.2": ["skylift"], "20.1 19.5 17.3": ["repopulates"], "21.5 8.8 38.7": ["medaka"], "13.0 19.1 12.9": ["beardie"], "7.9 3.6 7.2": ["opporutnity"], "2.8 4.2 12.1": ["biglycan"], "2.9 12.6 14.2": ["silentbobdrummer"], "3.6 18.1 0.2": ["confidance"], "2.3 3.9 6.7": ["implementating"], "-0.6 0.8 11.9": ["incrase"], "3.6 3.7 20.3": ["chenin"], "9.3 5.7 14.9": ["anthraquinone"], "6.3 8.1 17.3": ["unwooded"], "14.9 9.8 24.1": ["coxcomb"], "2.4 10.6 11.1": ["conse"], "-4.6 7.6 6.9": ["cooping"], "12.6 -6.4 18.2": ["mezzotints"], "12.4 1.7 -2.4": ["yestreday"], "14.6 3.3 14.3": ["swaged"], "16.8 29.9 19.5": ["durst"], "11.5 7.6 6.9": ["angkasawan"], "8.8 -1.7 19.2": ["pated"], "11.3 4.4 9.1": ["scooterettes"], "5.1 5.6 -8.5": ["aproval"], "11.4 18.7 13.3": ["searchin"], "8.2 19.9 12.5": ["happenes"], "9.1 30.8 3.8": ["machinated"], "0.0 2.5 10.8": ["spons"], "6.4 16.7 5.5": ["sloganeer"], "3.5 -7.6 4.2": ["compline"], "10.7 7.7 11.9": ["eko"], "-1.7 -12.5 2.3": ["webstreamed"], "3.4 12.1 0.5": ["complimentarity"], "10.6 0.0 12.3": ["nonstock"], "8.5 8.4 11.6": ["airblowers"], "8.6 14.1 21.0": ["achromatopsia"], "8.5 20.6 33.2": ["mudsnails"], "8.4 1.7 22.1": ["nailpolish"], "9.2 3.8 14.2": ["supermart"], "11.1 -2.2 11.7": ["guilloche"], "12.6 13.7 15.3": ["unreclaimed"], "14.5 15.8 13.1": ["abiogenesis"], "-10.0 -3.7 10.9": ["sopho"], "7.4 7.1 10.1": ["caterwauls"], "13.2 7.6 30.4": ["deckle"], "5.9 14.1 8.4": ["photosensitizing"], "6.8 2.9 8.4": ["boricua"], "10.9 7.9 5.6": ["wheelclamper"], "14.0 29.7 15.8": ["galljdaj"], "15.3 -1.5 16.1": ["dicor"], "7.1 6.1 32.3": ["xiaolongbao"], "2.9 9.5 9.3": ["selfconscious"], "22.0 20.4 3.4": ["trustbuster"], "9.7 -2.7 4.3": ["fianl"], "9.4 20.7 13.3": ["faily"], "14.3 10.8 -0.4": ["undercapitalisation"], "-1.2 5.7 1.0": ["prulifloxacin"], "-12.6 7.9 -4.6": ["eaders"], "13.2 7.3 10.9": ["turbogenerators"], "5.0 13.6 2.9": ["refoundation"], "14.1 15.2 6.3": ["sophistications"], "21.4 22.4 30.3": ["backstroking"], "5.4 23.8 10.6": ["inconvertible"], "6.3 9.0 12.0": ["atas"], "1.5 12.5 1.9": ["killng"], "16.8 12.3 11.3": ["masker"], "5.0 -1.0 1.4": ["isbased"], "10.7 9.5 5.1": ["perfecter"], "4.5 0.7 3.7": ["omanoil"], "10.6 4.8 18.9": ["pampa"], "-15.4 14.6 3.4": ["chinuch"], "-3.6 0.8 6.1": ["besylate"], "4.5 22.3 10.0": ["bloodlettings"], "2.7 14.0 9.8": ["demodulating"], "6.4 1.6 -3.4": ["attent"], "4.2 3.7 6.4": ["berlinetta"], "-4.8 4.6 14.3": ["nonmetro"], "9.8 13.1 17.4": ["stetched"], "6.0 7.6 8.8": ["tournamen"], "16.8 3.7 18.9": ["electroplate"], "14.4 5.3 27.3": ["anaheim"], "-0.6 15.2 11.4": ["kitab"], "5.7 15.5 25.4": ["intraspecific"], "25.5 17.9 10.2": ["lightcycles"], "12.4 15.8 1.8": ["bania"], "4.6 6.3 20.6": ["duckpin"], "-3.2 6.0 16.5": ["usse"], "0.2 -9.7 3.5": ["fte"], "6.4 3.6 7.9": ["rebab"], "4.5 16.8 19.1": ["watertable"], "15.3 11.2 15.8": ["sommer"], "3.0 3.9 22.7": ["bahiagrass"], "2.2 21.8 5.7": ["chalkface"], "3.4 10.5 7.6": ["intermetallic"], "6.5 -5.0 13.2": ["barongs"], "6.3 23.0 8.2": ["haterz"], "15.9 7.6 21.3": ["dissolver"], "12.7 1.4 0.5": ["diplayed"], "4.6 11.5 5.2": ["recordbooks"], "-1.0 12.6 7.0": ["galectins"], "21.7 2.1 15.2": ["kidvid"], "9.8 13.9 10.6": ["defunds"], "4.3 -2.2 14.9": ["editioned"], "1.5 6.3 13.3": ["madali"], "-6.5 9.5 8.3": ["monotonically"], "-1.4 1.1 9.2": ["cheilitis"], "5.1 13.1 14.9": ["monocots"], "5.7 6.8 7.4": ["theyr"], "3.6 44.9 8.4": ["skirmishers"], "27.9 23.3 15.2": ["insectlike"], "3.7 -1.1 7.3": ["intervarsity"], "3.4 7.0 15.3": ["amigas"], "19.7 7.6 13.0": ["flatpanel"], "15.3 11.4 9.7": ["murti"], "10.0 4.5 46.7": ["yellowtails"], "-6.5 -4.8 4.9": ["theboard"], "9.9 16.8 24.3": ["gutta"], "11.8 10.6 25.7": ["landlock"], "10.0 3.1 12.4": ["aromatherapeutic"], "4.7 6.7 9.5": ["bumpily"], "9.9 2.9 24.4": ["ziplock"], "19.3 19.5 14.7": ["strangelet"], "7.3 1.2 12.6": ["lapdances"], "12.7 7.2 17.9": ["volumising"], "1.7 7.5 11.5": ["ikun"], "0.4 19.2 8.6": ["offbase"], "3.0 5.0 18.8": ["ethnobotanical"], "-4.0 17.8 5.6": ["decribe"], "16.9 11.8 14.1": ["washhouse"], "-4.5 6.7 3.9": ["dicasteries"], "6.8 13.7 7.2": ["revivable"], "6.1 4.7 12.0": ["unjuried"], "14.7 -5.0 14.8": ["apx"], "12.8 2.4 17.4": ["mudbaths"], "8.4 18.9 1.2": ["lobbyism"], "2.3 14.4 10.7": ["bumis"], "1.4 6.0 23.4": ["chambourcin"], "2.1 6.8 -1.3": ["naukri"], "-7.9 -2.2 4.7": ["releaguing"], "15.8 4.3 20.9": ["qiu"], "-2.0 0.4 11.3": ["pontine"], "2.7 27.3 17.0": ["underhooks"], "7.6 5.8 8.6": ["mechanotransduction"], "1.4 4.9 25.0": ["vidal"], "2.6 -3.1 0.8": ["insu"], "7.0 16.6 10.5": ["fuckups"], "3.7 5.5 17.2": ["howe"], "-3.0 -1.6 0.1": ["entrylevel"], "4.9 16.4 3.7": ["autodidacts"], "3.8 10.7 9.2": ["pediculosis"], "22.8 5.5 26.1": ["circlet"], "2.5 4.4 8.0": ["transcriptionally"], "13.6 12.4 4.7": ["theenvironment"], "18.1 9.8 20.2": ["stx"], "13.9 2.7 1.5": ["nonprint"], "4.6 9.1 8.9": ["werenot"], "2.6 -0.7 12.2": ["ffordd"], "9.3 2.6 10.9": ["aja"], "24.7 4.7 -2.7": ["whizzkids"], "8.5 7.4 24.4": ["cloacal"], "18.1 15.8 10.0": ["spherically"], "1.5 6.4 7.0": ["nulling"], "-3.3 -0.5 5.3": ["imprests"], "5.4 2.2 14.8": ["pieds"], "0.7 7.2 18.7": ["magka"], "-6.4 16.0 6.1": ["parashah"], "7.7 -4.7 -2.5": ["otoscopes"], "18.1 10.3 5.9": ["venturer"], "1.2 5.9 18.1": ["morna"], "5.5 9.8 11.0": ["isk"], "-2.2 23.3 11.5": ["letups"], "-0.1 4.8 15.6": ["pinag"], "10.3 9.1 6.6": ["yestereday"], "13.7 -2.0 14.3": ["gurls"], "7.6 6.7 4.6": ["varietyof"], "-3.3 3.5 12.9": ["lawson"], "-5.1 1.9 9.3": ["aieee"], "5.3 16.1 5.3": ["stressfull"], "12.2 6.3 12.5": ["drawerful"], "19.0 27.9 8.6": ["telescreens"], "18.1 7.2 15.4": ["slagheap"], "1.4 18.0 3.0": ["allign"], "6.2 27.2 3.6": ["rightest"], "5.9 20.3 8.7": ["nonexisting"], "4.1 6.8 2.1": ["nextel"], "5.3 13.2 10.0": ["timeand"], "13.8 -1.2 6.1": ["craiglist"], "5.3 26.9 3.1": ["distorters"], "3.6 11.2 -0.3": ["countercheck"], "10.8 2.4 13.4": ["finalmente"], "2.4 10.3 0.4": ["washingtonpost"], "2.3 9.3 15.0": ["robson"], "12.6 7.1 16.9": ["ghungroos"], "13.3 -1.2 1.5": ["infosys"], "4.5 13.7 13.8": ["acquifers"], "10.4 8.6 7.7": ["cabrios"], "-1.4 17.3 5.4": ["hagiographical"], "1.8 7.5 -2.5": ["yearsand"], "7.3 16.6 10.9": ["wideangle"], "3.1 1.9 -2.8": ["thehome"], "-7.7 -4.3 11.4": ["postmenopause"], "5.4 1.5 11.3": ["detangler"], "2.2 9.0 12.5": ["alag"], "2.8 4.3 5.7": ["hydrolytic"], "-1.5 21.9 11.4": ["haye"], "0.4 21.8 2.0": ["squard"], "-0.3 2.8 1.2": ["diabled"], "-2.8 6.3 6.0": ["ount"], "-0.1 15.1 15.5": ["sanam"], "13.4 10.7 14.0": ["ultrathins"], "9.0 -2.9 17.6": ["fert"], "-6.0 9.4 7.3": ["teer"], "11.5 9.4 8.0": ["reflows"], "1.2 19.8 3.3": ["economistic"], "4.6 8.2 9.5": ["rapidement"], "9.1 8.3 5.1": ["gerade"], "3.3 17.9 8.7": ["incrementalists"], "3.1 16.4 8.1": ["snippiness"], "9.5 13.2 1.7": ["footwarmers"], "13.2 14.5 25.4": ["foodwise"], "6.9 15.2 8.1": ["brazilians"], "5.8 15.0 5.4": ["venerability"], "4.2 0.2 3.6": ["higherthan"], "1.6 4.7 11.3": ["curioser"], "17.9 2.2 28.5": ["chucky"], "10.5 11.8 16.7": ["cutted"], "12.1 9.1 27.1": ["thylacines"], "-6.8 4.2 14.2": ["dizygotic"], "2.9 16.4 13.5": ["gorefests"], "6.3 7.2 19.0": ["fum"], "10.7 21.8 0.4": ["activits"], "20.2 14.3 24.3": ["stranglers"], "9.4 11.8 22.8": ["tailers"], "6.6 19.0 14.1": ["weasly"], "12.4 15.6 -2.5": ["denationalized"], "8.5 28.9 2.9": ["mutliplayer"], "6.9 4.1 5.9": ["costof"], "7.8 15.2 20.9": ["gambiae"], "3.8 -9.7 1.5": ["mosimage"], "9.4 9.0 1.7": ["superintends"], "2.8 23.1 5.9": ["frustating"], "16.3 -3.2 19.9": ["twomonth"], "1.9 12.5 10.5": ["falsifiability"], "3.0 10.2 13.5": ["makaan"], "9.6 10.9 10.5": ["soakaway"], "-1.4 5.7 10.4": ["intrathoracic"], "19.9 11.5 21.7": ["ecosytem"], "13.5 17.0 14.5": ["inutility"], "7.1 8.7 8.9": ["seatliners"], "1.3 -2.9 2.1": ["ference"], "1.5 1.1 11.4": ["gambus"], "5.3 1.9 10.2": ["diarise"], "8.4 -1.4 30.5": ["tostados"], "10.4 16.2 17.4": ["snowcovered"], "16.6 27.9 24.4": ["chocobos"], "2.8 -4.9 -4.2": ["pressconference"], "3.3 11.4 7.8": ["metallisation"], "-6.9 -1.6 3.1": ["agendize"], "-4.1 9.6 1.9": ["certificateholders"], "13.1 21.9 10.1": ["execration"], "10.2 23.4 13.4": ["immobilises"], "3.2 11.7 0.9": ["importnat"], "11.8 21.3 3.8": ["overun"], "3.1 8.9 15.3": ["totoong", "magkasama"], "6.0 3.2 13.9": ["pangalan"], "3.3 1.4 16.4": ["joget"], "14.2 24.1 13.3": ["mindscapes"], "-8.1 6.2 8.8": ["pagbabago"], "5.5 17.5 -0.8": ["negotiatiors"], "2.8 15.7 6.4": ["earnable"], "5.0 -6.4 0.3": ["sociaux"], "9.9 25.5 6.2": ["villainizing"], "-2.9 6.8 19.0": ["neuroblasts"], "26.9 2.6 0.7": ["megaretailer"], "14.3 2.5 13.1": ["dobby"], "9.3 10.9 14.9": ["ojo"], "-2.5 6.6 0.6": ["signalize"], "13.3 1.3 11.5": ["waitering"], "7.4 7.5 25.7": ["sabji"], "2.4 -0.9 17.3": ["presyo"], "9.1 11.4 -2.8": ["wegen"], "2.7 2.8 9.0": ["isosorbide"], "19.4 13.1 14.1": ["spavined"], "6.0 12.4 13.6": ["guam"], "0.8 1.1 6.5": ["noncontractual"], "8.1 23.1 9.0": ["depersonalised"], "9.0 14.9 6.5": ["familair"], "20.1 8.2 12.6": ["enducing"], "10.7 2.4 20.7": ["kew"], "1.7 14.6 2.0": ["demotivates"], "16.4 -2.9 2.7": ["esimated"], "6.8 11.2 8.8": ["chelseaforever"], "14.4 14.2 16.1": ["raquet"], "-4.3 1.4 6.7": ["bemore"], "13.6 11.8 17.9": ["floorman"], "-1.7 13.9 14.5": ["alomost"], "12.4 8.4 5.3": ["flamable"], "22.6 1.1 9.6": ["citibank"], "20.4 10.4 12.7": ["tininess"], "6.4 15.1 9.0": ["encephalitic"], "6.4 22.9 -2.1": ["disinformed"], "-0.2 11.7 11.2": ["hiswife"], "20.2 28.1 20.9": ["popguns"], "13.4 12.1 30.1": ["ghillies"], "0.6 7.6 2.5": ["variational"], "-1.0 1.3 4.5": ["hyperhomocysteinemia"], "9.6 7.6 6.6": ["bodyache"], "17.5 5.6 8.2": ["ramraid"], "24.6 13.5 6.4": ["clockface"], "1.1 7.5 -5.1": ["administators"], "1.9 9.1 -1.9": ["folow"], "14.9 3.5 14.9": ["contessa"], "11.9 15.3 22.9": ["braincells"], "17.7 18.6 26.6": ["brogans"], "3.9 5.6 7.7": ["egal"], "6.7 23.7 29.8": ["ameba"], "2.1 -0.7 7.8": ["antiphons"], "6.5 8.9 6.9": ["detariffed"], "5.8 25.6 -4.2": ["potray"], "-9.7 6.7 -0.1": ["studentathletes"], "1.8 2.8 8.6": ["accompaning"], "-5.9 16.0 5.8": ["simpliciter"], "10.1 25.2 9.8": ["plottings"], "10.0 6.8 19.9": ["rubberlike"], "1.3 4.6 6.8": ["accounta"], "13.3 5.1 2.6": ["enfish"], "26.1 4.7 14.2": ["blackstone"], "3.7 6.6 15.5": ["pict"], "-6.6 12.1 7.0": ["multiethnicity"], "7.0 7.9 12.9": ["whoas"], "13.7 3.8 18.7": ["pumpable"], "2.5 25.6 1.6": ["civl"], "19.6 9.6 7.8": ["rse"], "19.0 4.5 16.5": ["barebacked"], "2.2 9.8 15.5": ["dimethoate"], "9.1 6.2 10.8": ["alguna"], "3.6 7.5 14.8": ["gott"], "-1.6 3.0 8.3": ["pede"], "11.8 -0.4 4.7": ["worldrenowned"], "16.3 11.6 22.8": ["ornamentally"], "7.1 -6.9 17.1": ["charolais"], "14.0 5.6 -3.8": ["hasbecome"], "8.3 14.8 4.3": ["remotivated"], "8.1 6.8 17.3": ["paleomagnetism"], "5.1 2.2 11.5": ["clientes"], "10.7 18.2 30.0": ["spireas"], "12.5 10.5 11.9": ["pebbledash"], "-1.4 3.9 6.3": ["methodologists"], "1.3 -7.9 -2.0": ["inb"], "7.7 8.5 9.9": ["conveyorized"], "13.7 3.9 9.4": ["nanobiology"], "-4.0 0.0 2.5": ["evin"], "10.5 25.7 0.7": ["couragous"], "5.9 10.6 -2.4": ["immunises"], "10.7 6.7 7.9": ["handel"], "4.6 25.3 5.6": ["principalists"], "8.0 18.7 12.6": ["snobberies"], "7.2 8.6 16.5": ["clopyralid"], "12.8 6.4 12.7": ["fluorometer"], "-7.9 5.6 3.3": ["socre"], "9.7 9.5 6.1": ["deptartment"], "-3.3 8.6 -2.1": ["inconsistences"], "5.0 17.2 9.0": ["contactees"], "-2.8 6.2 3.3": ["shabads"], "4.8 20.4 14.8": ["shiftiest"], "7.5 19.5 14.3": ["pheromonal"], "7.1 5.9 17.8": ["mowa"], "-3.1 5.3 2.5": ["liened"], "4.2 9.0 16.4": ["swa"], "10.9 2.2 20.0": ["slushed"], "12.2 11.3 4.1": ["loooot"], "12.9 -3.7 3.2": ["geeft"], "8.8 13.4 13.4": ["repetative"], "9.6 6.0 21.0": ["mayonnaises"], "8.6 4.3 2.4": ["avions"], "6.1 20.5 -0.4": ["steganographic"], "-1.5 7.4 -1.2": ["campa"], "4.2 16.1 9.4": ["cofigure"], "6.1 3.6 -2.6": ["zusammen"], "6.8 9.3 5.0": ["remaind"], "21.6 28.2 22.5": ["rabbids"], "7.5 24.9 6.7": ["despisers"], "3.8 -0.4 3.9": ["vides"], "-0.3 0.9 11.3": ["ruta"], "11.2 9.7 13.2": ["begans"], "-2.9 17.1 0.0": ["deradicalisation"], "-1.9 6.8 18.2": ["tatay"], "5.0 3.7 8.6": ["intradermally"], "16.8 7.4 27.4": ["cassata"], "5.1 6.2 18.4": ["unga"], "8.8 7.1 16.0": ["caravaners"], "-0.6 14.1 3.3": ["condemmed"], "8.8 5.9 27.0": ["kirby"], "30.2 13.8 32.7": ["paddlewheels"], "-8.1 15.3 0.8": ["colleauges"], "2.2 1.8 9.7": ["huperzine"], "6.6 9.1 15.4": ["tatau"], "3.6 14.5 6.4": ["relucant"], "-0.8 7.3 13.7": ["intronic"], "-2.8 -4.4 12.0": ["subadvises"], "5.4 7.4 17.5": ["dumating"], "7.1 17.3 17.8": ["unmooring"], "-2.6 5.3 4.2": ["recom"], "4.9 19.6 0.9": ["decompile"], "7.6 8.2 25.3": ["tsampa"], "-0.4 8.4 14.5": ["pumunta"], "-1.5 13.2 3.2": ["clarities"], "0.8 17.2 13.7": ["peron"], "17.1 25.7 12.1": ["encaged"], "8.0 15.9 10.8": ["breakoff"], "9.7 15.3 21.6": ["hatchers"], "-0.5 17.6 -1.0": ["inapropriate"], "9.1 -2.2 7.2": ["eurocent"], "3.3 8.9 16.1": ["semiserious"], "1.2 5.1 9.1": ["carfree"], "7.2 19.8 13.1": ["ipconfig"], "12.9 8.9 9.7": ["danfo"], "-7.1 -4.8 2.1": ["conce"], "7.0 -4.1 2.1": ["affilliate"], "7.8 10.4 8.4": ["morse"], "15.7 10.3 14.3": ["nontechnology"], "-4.7 17.9 4.4": ["usto"], "1.4 6.3 14.4": ["sublayer"], "14.7 15.7 17.9": ["greasewood"], "-5.6 6.6 -0.2": ["memorizers"], "-5.1 17.4 4.1": ["heve"], "9.3 5.3 3.1": ["triumped"], "-0.5 5.5 -2.9": ["transferors"], "10.0 -2.9 33.9": ["donairs"], "4.1 8.7 -0.9": ["newswriters"], "10.5 13.6 12.7": ["thatches"], "6.5 1.4 11.8": ["alomst"], "11.6 0.3 23.3": ["minxy"], "11.0 4.7 21.4": ["mixto"], "3.4 12.4 11.0": ["hoodless"], "-8.8 -6.1 0.8": ["euthyroid"], "-2.5 5.4 28.5": ["lambrusco"], "-5.1 17.1 4.1": ["predicator"], "-3.2 0.3 6.1": ["revoting"], "15.3 4.7 7.3": ["epater"], "18.4 10.8 22.5": ["lyrebird"], "14.0 2.4 10.3": ["multihour"], "2.3 8.8 9.4": ["racetime"], "2.5 24.2 3.0": ["dejecting"], "0.7 1.1 10.4": ["lombard"], "21.3 5.7 3.2": ["ligitation"], "-5.2 1.1 -0.4": ["succimer"], "2.1 9.6 4.8": ["tumorigenicity"], "1.8 14.5 10.3": ["syringing"], "17.7 -1.1 23.2": ["tinsmithing"], "6.7 7.1 10.0": ["taling"], "10.7 3.4 6.5": ["forr"], "4.8 7.4 14.2": ["bellissimo"], "-3.1 1.1 1.0": ["potentiostat", "battent"], "1.7 -9.3 -5.0": ["announcd"], "17.4 21.9 29.2": ["snuffer"], "21.9 23.1 11.1": ["soros"], "-1.5 2.7 4.9": ["rif"], "15.0 7.6 20.9": ["cointreau"], "20.2 8.1 18.6": ["flappin"], "13.2 10.7 11.9": ["fiveminute"], "0.7 4.0 5.9": ["titleists"], "-5.3 13.5 2.4": ["overide"], "-0.3 6.2 18.1": ["pola"], "13.7 10.9 6.5": ["unpenetrated"], "5.0 -5.3 20.3": ["primestock"], "7.0 3.8 24.4": ["glabra"], "10.2 9.3 16.4": ["muchachos"], "0.9 12.0 12.3": ["nonblacks"], "-4.2 8.1 9.5": ["streamgages"], "9.7 19.9 15.5": ["inhabitated"], "-3.5 10.3 7.5": ["demandable"], "19.5 14.3 15.9": ["rubbernecker"], "26.3 5.8 19.3": ["forklifted"], "6.5 -1.4 -0.9": ["delicensed"], "6.7 3.1 45.6": ["pipis"], "13.4 18.9 3.5": ["perqs"], "8.3 16.1 17.6": ["dropshipper"], "0.2 27.2 6.5": ["disserving"], "3.0 27.3 6.7": ["naieve"], "13.1 3.7 27.1": ["cottagey"], "19.3 20.2 40.0": ["tenderise"], "-0.1 4.7 0.7": ["anorgasmia"], "18.5 14.3 5.4": ["yuhangyuan"], "20.2 15.1 29.2": ["cricks"], "-5.4 13.1 -1.8": ["attunes"], "12.7 11.0 15.0": ["biospheric"], "10.4 0.8 26.9": ["chua"], "10.0 12.0 14.8": ["paranormals"], "16.4 -0.6 -1.1": ["devleopment"], "13.3 -2.4 2.3": ["catwalked"], "15.6 17.2 16.7": ["downthe"], "11.3 17.6 16.8": ["paleface"], "9.3 4.3 27.1": ["pisang"], "8.8 13.1 29.4": ["vincas"], "8.7 4.5 2.8": ["exluding"], "19.3 6.2 22.5": ["bonzer"], "3.7 4.8 4.7": ["speacial"], "8.1 -6.7 1.8": ["eports"], "15.6 5.8 6.4": ["debugs"], "-11.1 5.7 3.8": ["lobectomies"], "9.2 23.0 9.0": ["millennialist"], "11.4 -5.1 16.7": ["shelflife"], "-3.2 -1.1 6.0": ["guestings"], "-6.1 0.6 -2.6": ["complaince"], "-1.7 2.1 2.9": ["chemometrics"], "11.0 6.5 8.3": ["seroquel"], "4.2 29.4 7.8": ["brahmanical"], "5.5 2.8 13.1": ["azione"], "5.5 8.6 31.7": ["immatures"], "2.3 5.0 2.9": ["nonathlete"], "7.7 1.3 9.7": ["fanout"], "2.9 14.9 0.4": ["epigones"], "17.1 4.5 11.0": ["gyprock"], "17.5 5.6 20.4": ["screwtop"], "-4.6 22.5 5.1": ["insistant"], "14.1 11.3 6.0": ["foriegners"], "10.1 5.7 6.2": ["bioserie"], "3.9 2.0 3.3": ["swe"], "12.2 6.8 15.3": ["clits"], "5.5 5.9 12.9": ["backscattering"], "4.8 14.5 9.5": ["vomeronasal"], "1.3 -3.1 -0.0": ["kahr"], "-7.3 12.7 6.6": ["attritions"], "16.8 14.9 30.0": ["bearcats"], "4.2 21.9 4.6": ["nepali"], "16.1 11.5 9.4": ["businessfolk"], "3.1 1.8 -5.7": ["foootball"], "0.8 -4.1 15.5": ["duction"], "4.2 15.9 8.1": ["formalists"], "2.1 5.5 -2.0": ["charismathics"], "3.6 0.2 6.8": ["polysulfone"], "7.8 -1.2 6.6": ["wheelrace"], "2.6 16.4 2.4": ["beleave"], "16.0 8.0 12.8": ["booziest"], "10.6 17.9 15.9": ["puckline"], "10.2 15.9 8.8": ["tritone"], "6.4 12.4 14.0": ["seborrhea"], "5.5 14.8 7.9": ["pietism"], "3.6 8.4 12.8": ["pangulo"], "13.0 15.2 3.3": ["nehru"], "4.7 -1.6 8.4": ["gluconate"], "8.8 9.7 8.2": ["competitition"], "9.4 5.1 14.6": ["labret"], "8.9 2.4 16.4": ["pattu"], "5.4 13.5 18.3": ["cockfighter"], "8.1 13.3 14.0": ["chunter"], "5.8 2.5 14.1": ["pagar"], "21.7 14.8 20.5": ["cavewomen"], "9.6 13.8 5.4": ["roofspace"], "14.7 24.0 10.8": ["camer"], "7.8 13.5 9.7": ["orthogonally"], "4.4 17.0 15.5": ["defintiely"], "9.0 8.4 1.2": ["slamed"], "16.2 19.1 9.9": ["treemap"], "9.5 -4.4 11.6": ["hostings"], "6.1 23.2 8.3": ["disconcerts"], "16.1 6.3 6.5": ["gomesi"], "14.7 4.7 11.5": ["thebeginning"], "-4.5 11.7 13.3": ["intestates"], "13.9 14.7 15.6": ["wisecrackers"], "12.1 22.9 11.2": ["gullable"], "18.7 -9.4 11.4": ["tubings"], "0.4 9.8 7.8": ["andthere"], "6.2 8.8 8.0": ["msu"], "7.0 4.2 6.8": ["resequenced"], "-0.6 19.4 13.1": ["uneasiest"], "4.3 10.7 9.5": ["entablature"], "5.8 3.9 2.9": ["electrocatalysts"], "1.6 -1.5 9.9": ["wri"], "7.4 6.6 24.6": ["clearwater"], "1.9 2.8 -2.7": ["thermopile"], "5.8 29.7 1.9": ["acquiesence"], "1.4 8.1 -2.1": ["criti"], "-1.5 4.5 7.7": ["findout"], "5.7 4.2 0.5": ["novate"], "3.4 6.5 9.3": ["bels"], "9.0 13.8 2.4": ["lensless"], "1.1 20.6 4.9": ["gnostics"], "16.2 7.7 14.2": ["magnifico"], "3.2 -0.4 9.7": ["fructan"], "2.8 -1.8 18.8": ["gimmers"], "-1.8 28.7 0.3": ["refuser"], "6.2 16.0 5.0": ["adaptivity"], "9.9 -9.1 3.8": ["condominums"], "3.3 6.0 7.3": ["postcollege"], "12.4 7.7 22.7": ["hogsheads"], "13.7 4.2 3.6": ["cobranding"], "-3.1 13.6 4.8": ["censorships"], "12.4 9.7 15.9": ["splasher"], "9.7 5.8 5.4": ["progarmme"], "13.6 13.0 16.9": ["knobbies"], "3.1 1.4 17.2": ["ramsey"], "1.7 5.5 3.4": ["monologists"], "6.8 13.8 8.0": ["supergrasses"], "11.0 11.7 2.5": ["nexis"], "3.3 20.1 11.8": ["intriguers"], "11.0 4.4 13.6": ["cardis"], "3.9 17.3 6.0": ["ofit"], "7.5 10.3 16.7": ["lolas"], "12.3 11.9 16.6": ["dfwjustin"], "0.2 -6.3 7.5": ["culturelle"], "-6.6 11.9 4.1": ["pharmacotherapeutics"], "1.1 0.6 10.7": ["khatas"], "9.5 8.9 11.8": ["encierro"], "17.1 5.3 11.5": ["shortcircuit"], "14.8 12.0 -7.8": ["simulataneously"], "-0.9 -5.3 17.9": ["olein"], "11.5 11.7 9.9": ["brahma"], "4.7 0.9 15.5": ["avon"], "-10.4 19.7 3.8": ["surrenderee"], "16.4 1.6 21.5": ["luncheonettes"], "17.8 23.1 18.1": ["loogies"], "14.6 17.7 8.6": ["distaster"], "11.0 10.5 26.2": ["racemosa"], "9.2 -4.1 8.7": ["overyear"], "9.8 10.0 28.8": ["instars"], "3.9 16.4 12.5": ["shankar"], "12.2 21.1 22.1": ["birdcall"], "6.3 21.9 7.2": ["unprecedently"], "5.5 10.9 37.6": ["sportsfishing"], "-4.6 7.6 -0.7": ["avantage"], "2.4 14.4 7.9": ["dispensational"], "6.9 5.1 -1.3": ["plce"], "9.4 21.0 18.2": ["glibbest"], "2.2 -7.9 6.2": ["consulter"], "19.6 -8.2 14.7": ["scrubbies"], "4.6 -4.4 8.8": ["acy"], "-5.0 3.5 0.9": ["immunopathology"], "11.4 9.3 12.6": ["saucered"], "24.7 3.5 24.1": ["scourers"], "0.6 10.5 7.1": ["komatiitic"], "10.7 14.2 11.1": ["midtrial"], "14.2 16.7 15.8": ["unsaddle"], "10.9 29.0 8.1": ["heathenism"], "-2.6 -0.0 6.3": ["degradability"], "2.9 -3.1 -2.0": ["asimadoline"], "11.6 14.2 16.8": ["aleatory"], "8.4 5.7 25.0": ["delectability"], "-6.3 13.3 3.8": ["solat"], "13.8 6.4 15.9": ["darvocet"], "14.1 16.7 21.4": ["baldhead"], "9.4 9.1 3.4": ["merdeka"], "-5.0 12.3 -1.6": ["cantt"], "-1.4 5.9 3.4": ["psychoneuroimmunology"], "0.7 -1.9 6.2": ["noncontract"], "5.4 -1.6 0.3": ["dihydrochloride"], "3.0 -0.1 -7.1": ["demonstated"], "7.9 -3.4 1.8": ["anhour"], "9.5 12.3 31.3": ["sifakas"], "-2.7 13.8 5.1": ["resonation"], "8.9 12.4 16.4": ["stargazed"], "7.6 11.5 4.9": ["becker"], "6.4 20.8 4.2": ["clownishness"], "5.6 0.2 -3.6": ["fivestar"], "12.1 -5.9 20.3": ["bridies"], "5.0 13.5 3.1": ["propostion"], "12.0 26.1 3.3": ["manouver"], "0.5 -9.4 -7.2": ["appreared"], "12.9 2.1 34.8": ["acquaculture"], "9.8 9.8 12.1": ["oversleeps"], "2.8 8.2 12.4": ["bluegrassers"], "6.6 13.8 8.0": ["danke"], "-0.9 -0.0 6.6": ["toraise"], "5.8 10.8 13.9": ["lindastern"], "7.9 2.6 31.7": ["pulut"], "5.4 25.7 2.4": ["neutralism"], "5.1 14.8 2.7": ["hearby"], "10.8 5.3 13.3": ["slub"], "11.3 4.0 2.8": ["downscales"], "-6.5 5.8 -1.2": ["immunoconjugate"], "4.4 12.1 1.5": ["paticularly"], "14.2 1.1 31.6": ["ensalada"], "15.3 26.7 3.7": ["manipulatable"], "27.7 6.5 15.1": ["vertising"], "1.2 12.5 10.3": ["stripline"], "3.5 2.4 10.7": ["itions"], "14.5 8.9 18.2": ["minge"], "-0.2 16.8 5.6": ["policial"], "-4.5 3.2 0.2": ["omra"], "9.4 6.2 11.2": ["distrubuted"], "13.9 19.7 6.6": ["greate"], "13.7 7.9 17.1": ["placentals"], "2.0 4.1 27.8": ["vermentino"], "8.3 12.9 11.8": ["peoople"], "-5.3 7.1 3.7": ["leukoreduction"], "8.3 4.7 27.0": ["goldish"], "-5.8 11.7 4.5": ["ethe"], "17.5 29.2 19.5": ["halfling"], "14.2 12.1 19.0": ["gunstock"], "12.6 7.8 15.1": ["kyeong"], "15.3 14.9 19.3": ["garrotting"], "9.9 11.1 5.7": ["structureless"], "9.0 1.6 -1.6": ["testdrive"], "-5.0 7.7 10.4": ["picomolar"], "7.0 1.8 15.3": ["brok"], "25.5 15.5 24.5": ["slushee"], "2.5 1.0 8.2": ["geneva"], "9.6 12.6 8.9": ["propect"], "-4.3 -3.0 8.7": ["invisalign"], "1.2 24.2 2.9": ["misguides"], "-4.3 1.1 8.1": ["endothelialization"], "6.4 11.6 9.9": ["plannin"], "22.1 12.3 31.4": ["wagtail"], "17.8 10.4 27.7": ["pollywog"], "-6.8 10.1 5.3": ["stam"], "8.2 -1.8 17.7": ["jazzfest"], "-4.9 3.3 6.7": ["phimosis"], "-2.0 0.9 9.2": ["hypomethylation"], "2.6 16.3 10.8": ["burlgary"], "-3.5 4.6 0.2": ["thalassemic"], "4.2 9.1 -0.7": ["evern"], "14.6 6.6 8.1": ["hotest"], "-1.5 5.5 13.6": ["kandidato"], "12.4 6.7 -7.1": ["wherehe"], "-2.6 8.3 4.2": ["elimate"], "3.1 11.6 10.3": ["corrosivity"], "-1.2 -3.7 5.0": ["lready"], "7.7 16.5 16.2": ["disproportioned"], "14.5 0.3 12.7": ["prodution"], "2.9 4.3 17.0": ["joshes"], "4.6 18.2 1.9": ["delinks"], "1.1 5.2 5.0": ["toxicologic"], "11.7 0.7 -7.1": ["upstreamed"], "5.9 14.0 14.8": ["flaired"], "4.2 25.3 19.4": ["wingbone"], "-2.6 -1.2 6.7": ["repres"], "-3.7 11.5 9.2": ["lifecos"], "4.8 6.0 12.3": ["funemployment"], "-0.1 7.9 5.4": ["supersubs"], "3.2 4.5 2.9": ["conflictions"], "2.5 0.6 2.4": ["mitra"], "23.1 2.3 21.6": ["greengrocery"], "-4.6 14.0 4.7": ["croatia"], "7.8 -0.3 12.3": ["zenegra"], "1.1 9.8 2.1": ["grup"], "9.8 14.4 4.7": ["publicaly"], "5.3 8.2 8.4": ["irritancy"], "3.9 16.7 7.1": ["antidevelopment"], "6.6 -6.0 12.2": ["switchplates"], "10.1 19.8 17.7": ["ulimately"], "13.1 3.8 12.3": ["tasisulam"], "7.4 6.9 10.9": ["sioux"], "18.5 15.5 5.3": ["poping"], "1.7 16.2 2.6": ["starers"], "8.1 18.0 41.9": ["bronzebacks"], "1.9 4.5 2.5": ["gradeschool"], "-9.4 13.0 11.6": ["agunah"], "0.6 -1.9 16.1": ["methylhexanamine"], "8.4 5.6 12.8": ["merengues"], "-0.5 -0.6 12.6": ["osteosynthesis"], "-7.0 7.4 6.6": ["parenterally"], "4.2 7.4 7.5": ["rslack"], "22.4 0.4 26.7": ["steakburgers"], "13.5 19.3 14.3": ["arras"], "13.1 3.8 6.0": ["undeciphered"], "12.1 -4.9 13.9": ["taa"], "7.2 9.9 26.3": ["salina"], "-8.6 -2.7 -0.7": ["nonelective"], "11.8 16.8 11.5": ["ruiner"], "-0.4 1.1 13.4": ["paraan"], "-3.2 11.9 6.6": ["provo"], "8.9 14.4 15.1": ["uneconomically"], "20.8 31.5 12.9": ["lightsabres"], "10.5 6.2 12.6": ["risc"], "6.9 9.5 4.4": ["ionise"], "4.4 24.0 8.0": ["unhyphenated"], "5.3 0.1 10.3": ["geol"], "8.4 9.6 6.2": ["governmetn"], "17.0 9.1 12.5": ["jackleg"], "5.6 17.7 14.5": ["antineutrino"], "-1.5 1.7 6.0": ["remediators"], "-6.0 12.3 11.1": ["parshah"], "9.1 11.8 6.2": ["detemined"], "15.1 2.6 17.2": ["chicky"], "11.6 4.9 24.3": ["dolci"], "-1.1 7.3 9.6": ["demureness"], "8.8 13.7 16.5": ["pictu"], "-9.4 7.0 6.0": ["hemodilution"], "10.2 11.2 14.2": ["icewater"], "4.0 12.6 16.9": ["strattera"], "-8.1 6.2 8.1": ["maski"], "2.6 2.1 7.4": ["drillcore"], "13.6 12.9 4.8": ["peddlars"], "3.9 9.4 9.4": ["spielen"], "9.5 12.5 13.3": ["guang"], "10.3 -1.5 14.2": ["velum"], "14.2 15.5 11.8": ["stange"], "10.5 10.2 25.3": ["oakleaf"], "10.5 0.5 0.9": ["ofhigh"], "7.8 -0.1 -2.8": ["publised"], "7.4 23.8 3.0": ["beleiving"], "11.1 10.8 10.4": ["underfinancing"], "10.7 2.6 -5.7": ["electrometer"], "2.0 1.6 12.1": ["droga"], "-3.8 -6.8 1.7": ["mentre"], "5.4 6.7 21.1": ["farmette"], "10.2 1.9 -3.9": ["respresents"], "18.7 9.9 15.4": ["organotins"], "-2.6 14.5 9.2": ["undeclareds"], "2.9 12.5 7.9": ["toure"], "3.1 9.2 2.5": ["emancipates"], "2.4 3.8 6.1": ["ficial"], "9.8 9.3 -1.6": ["eyeshade"], "4.7 26.7 13.2": ["jujutsu"], "-0.3 17.6 7.9": ["contactee"], "9.4 11.9 4.1": ["outjumps"], "11.8 19.2 10.0": ["freebooting"], "8.1 8.3 8.0": ["misprice"], "9.5 -4.2 6.6": ["blubs"], "19.0 3.1 7.8": ["betterthan"], "6.9 -1.9 7.8": ["catalyser"], "15.0 6.2 5.0": ["baaing"], "2.3 22.4 -1.0": ["factionalization"], "9.3 4.0 17.5": ["santero"], "13.4 0.7 25.3": ["buchu"], "-0.4 13.3 7.0": ["puranas"], "7.1 2.6 6.8": ["centrotherm"], "1.7 1.8 22.3": ["moy"], "11.7 6.2 9.5": ["attactive"], "16.7 0.5 5.4": ["thesun"], "8.6 11.3 12.6": ["chaddi"], "9.8 16.9 11.7": ["symlinks"], "3.6 10.4 18.6": ["albicans"], "-7.6 -4.5 -3.9": ["secondyear"], "2.1 8.3 -1.9": ["makar"], "4.0 2.4 8.7": ["calcific"], "-4.5 -3.6 -5.2": ["rebaptized"], "8.6 3.1 12.5": ["nanomembranes"], "12.7 16.4 25.7": ["marshmellows"], "-0.1 7.6 -2.5": ["electrocatalyst"], "7.3 13.2 8.1": ["hitwoman"], "-1.5 14.1 14.9": ["untraditionally"], "-2.4 5.1 6.9": ["marketconditions"], "17.1 2.6 19.8": ["pyrex"], "17.2 2.0 35.2": ["reggiano"], "-2.4 6.8 -0.3": ["tez"], "-4.1 38.1 2.0": ["cmdr"], "8.5 -4.8 3.4": ["logi"], "-2.6 2.7 9.0": ["subtalar"], "7.5 22.5 5.0": ["maladapted"], "5.7 16.4 7.6": ["mutualist"], "12.0 13.6 7.5": ["pivo"], "6.0 9.6 15.3": ["strachan"], "2.8 -0.7 8.9": ["nervosa"], "17.2 7.6 21.2": ["pening"], "14.6 10.3 7.5": ["grasper"], "20.8 10.7 23.5": ["transluscent"], "8.3 8.7 8.9": ["inheritence"], "11.1 27.4 14.0": ["enchained"], "17.8 17.2 3.5": ["platensimycin"], "13.2 19.0 7.1": ["autogiro"], "10.0 7.0 22.7": ["tokay"], "11.5 15.4 24.8": ["lepidopteran"], "3.3 7.8 10.8": ["unbeleivable"], "7.6 12.2 5.7": ["isicathamiya"], "8.6 -0.6 5.7": ["entwickelt"], "3.4 4.5 7.4": ["ostial"], "0.1 7.6 2.2": ["semistructured"], "14.7 1.4 3.5": ["andgovernment"], "31.0 5.1 23.2": ["lifesized"], "7.7 18.7 7.9": ["gymnastically"], "10.1 1.1 21.7": ["rearer"], "2.7 1.1 7.9": ["broked"], "11.8 3.6 15.3": ["trix"], "0.3 2.8 7.8": ["trandolapril"], "14.2 17.0 10.8": ["starwars"], "9.2 20.5 12.2": ["torrentially"], "4.5 4.9 7.6": ["lae"], "7.9 6.5 12.1": ["dizi"], "-2.3 14.3 11.0": ["placentitis"], "8.6 9.8 6.6": ["doccie"], "12.4 13.6 25.2": ["mucilaginous"], "-5.7 10.9 6.0": ["fangraphs"], "7.9 9.5 9.1": ["onliners"], "-2.5 5.8 8.7": ["agreee"], "6.5 10.1 7.3": ["transitways"], "6.9 10.8 2.1": ["neurodiversity"], "-4.5 6.7 2.2": ["thedate"], "5.7 24.6 1.3": ["seditionist"], "2.5 6.8 0.2": ["immerged"], "15.2 26.2 28.2": ["leggeds"], "0.3 7.5 8.4": ["chulhas"], "8.3 5.7 6.2": ["namma"], "-9.8 8.7 10.0": ["sanggunian"], "4.9 13.4 14.0": ["mbenedict"], "8.6 19.7 12.5": ["unsaveable"], "19.8 11.7 18.8": ["cragged"], "-6.5 -5.7 1.1": ["exh"], "5.1 8.9 7.2": ["lelber"], "4.3 7.5 7.2": ["homemovers"], "10.5 25.1 8.0": ["nonracialism"], "5.4 19.1 2.0": ["punctiliousness"], "8.7 -2.2 5.1": ["lansing"], "12.6 9.0 12.8": ["nutplates"], "11.1 19.4 14.4": ["clonk"], "3.2 11.2 9.6": ["tighest"], "9.2 15.0 14.8": ["whippers"], "5.0 14.4 9.0": ["downballot"], "2.8 3.9 -1.8": ["agress"], "0.9 4.9 4.9": ["lipsync"], "8.3 20.8 9.1": ["undismayed"], "0.2 6.2 18.0": ["sidedress"], "5.0 6.1 10.2": ["intracounty"], "19.7 9.3 11.0": ["chicklet"], "11.6 0.9 18.0": ["pinta"], "8.4 -0.1 3.3": ["connectible"], "8.2 13.4 1.3": ["fianancial"], "8.0 11.1 4.2": ["retrocessionaires"], "20.1 17.0 12.7": ["glassless"], "5.4 11.7 18.1": ["sparklies"], "-5.7 -3.8 15.9": ["noncharter"], "4.7 9.8 10.6": ["electrolyzed"], "5.1 16.0 18.0": ["clonally"], "20.1 20.2 50.7": ["ribbonfish"], "2.2 14.1 2.2": ["liberte"], "7.2 10.9 9.5": ["jazziness"], "10.9 6.2 12.3": ["applier"], "1.4 11.8 17.9": ["totti"], "4.4 19.4 11.7": ["solidaristic"], "-0.6 22.3 9.5": ["chagrinned"], "2.9 -1.2 19.3": ["wooled"], "14.1 12.5 11.9": ["unhandy"], "4.0 10.0 11.7": ["monogenic"], "7.7 5.3 13.9": ["phosphite"], "14.8 15.3 7.8": ["penpushers"], "11.4 7.1 10.3": ["ecopreneurs"], "4.1 5.4 8.0": ["kihn"], "10.5 11.4 20.3": ["midtone"], "0.9 7.3 3.3": ["sehen"], "-1.7 3.2 15.8": ["nondrivers"], "1.3 1.1 28.8": ["matanza"], "15.1 23.4 12.7": ["peskier"], "-6.9 0.6 3.7": ["rell"], "6.0 11.4 5.7": ["unwellness"], "4.1 8.3 30.8": ["macroinvertebrate"], "22.4 11.2 10.2": ["railtracks"], "-3.5 16.2 9.3": ["sacramentals"], "10.6 2.4 10.6": ["nuhm"], "12.9 19.8 25.1": ["arrgh"], "10.8 15.4 18.3": ["jism"], "7.9 3.5 5.1": ["etailing"], "1.1 -1.1 6.3": ["ecole"], "0.6 13.9 10.4": ["bfore"], "1.1 8.1 5.5": ["sociodemographics"], "10.0 -0.1 3.6": ["informationtechnology"], "8.8 10.1 -1.2": ["futre"], "14.7 1.0 9.3": ["livered"], "8.4 16.1 13.4": ["misandrist"], "13.8 7.1 31.9": ["gulper"], "18.3 19.7 9.2": ["salutory"], "5.8 4.8 1.3": ["nanoscientist"], "13.3 12.9 25.0": ["starchiness"], "11.9 10.4 15.7": ["adagios"], "-4.0 10.2 8.5": ["gotras"], "16.9 2.8 8.6": ["tassa"], "4.6 12.2 8.9": ["rampancy"], "10.7 14.2 12.2": ["spellbindingly"], "30.5 15.1 31.7": ["peppermill"], "-4.7 7.6 2.8": ["rebuttle"], "15.1 11.5 9.6": ["finanicial"], "-0.1 1.6 -0.9": ["dkt"], "15.9 15.6 24.6": ["scabious"], "21.6 6.2 3.9": ["emblazened"], "-6.4 8.6 13.3": ["godsister"], "7.8 9.5 6.1": ["nauseas"], "-1.4 18.1 3.7": ["constitutionalized"], "1.9 16.8 6.2": ["scrobble"], "8.6 4.1 -2.2": ["robbensalter"], "6.1 3.3 10.5": ["panthenol"], "1.4 9.3 -1.6": ["intellectualproperty"], "11.2 1.4 14.8": ["cheroots"], "4.2 10.5 9.7": ["traditon"], "11.0 -2.3 11.6": ["musthave"], "12.6 23.8 1.9": ["revanche"], "-2.5 4.7 11.0": ["hunkier"], "10.9 8.1 6.5": ["arthritics"], "0.1 -9.5 5.5": ["interlibrary"], "4.7 2.2 6.0": ["journalling"], "14.0 6.6 1.5": ["ebanking"], "-1.8 12.2 11.4": ["bilkul"], "12.2 -4.4 4.4": ["persaude"], "2.8 -3.6 -12.1": ["onbehalf"], "6.1 6.5 5.0": ["feedthroughs"], "17.0 18.1 13.1": ["synform"], "-3.0 9.4 9.2": ["politika"], "3.6 14.0 3.0": ["tochange"], "-2.3 -6.1 9.7": ["sca"], "1.1 1.8 14.5": ["giorno"], "18.1 8.2 22.7": ["dieffenbachia"], "6.5 8.8 5.7": ["awy"], "3.1 2.6 3.9": ["hepatomegaly"], "12.4 16.8 26.6": ["mithun"], "3.1 -0.3 -3.0": ["antiplatelets"], "-2.8 7.9 7.0": ["antidilution"], "14.2 8.9 11.9": ["skronky"], "8.9 14.5 20.7": ["largazole"], "-0.4 10.2 8.5": ["virucidal"], "-2.6 2.9 -4.5": ["fsb"], "10.1 2.6 31.8": ["salumeria"], "-3.5 31.3 1.8": ["bloodsheds"], "2.2 8.0 5.8": ["etilefrine"], "-3.5 17.1 -3.1": ["hagiographer"], "10.8 13.3 25.2": ["xia"], "8.0 10.2 14.6": ["siloing"], "9.5 19.6 18.7": ["hawksdawgs"], "8.3 25.0 10.3": ["whosever"], "17.2 1.1 5.9": ["netlink"], "8.5 8.0 18.4": ["maiolica"], "1.5 7.3 2.7": ["periostin"], "-1.5 8.2 2.3": ["riociguat"], "5.5 7.1 15.6": ["kierin"], "1.5 -2.5 6.2": ["conted"], "3.0 9.2 -3.9": ["discusions"], "5.1 3.1 18.3": ["spermatogonia"], "12.9 23.2 19.0": ["gibing"], "9.5 1.4 2.5": ["contibution"], "6.9 7.3 10.2": ["shamianas"], "4.9 14.8 7.6": ["parivartan"], "-3.6 13.6 3.8": ["engrafting"], "12.1 8.6 18.2": ["loadsa"], "22.8 5.6 15.1": ["ooohing"], "2.9 5.3 -0.7": ["officing"], "17.9 11.9 25.1": ["scabiosa"], "17.5 3.1 9.7": ["schloss"], "10.3 15.8 9.2": ["alterego"], "10.9 5.7 2.3": ["lft"], "8.1 20.0 12.1": ["uncontrollables"], "9.3 12.0 13.1": ["ketu"], "10.9 -0.7 -1.7": ["facelifting"], "0.5 2.2 3.4": ["nazionale"], "-1.5 2.9 0.1": ["interinstitutional"], "12.9 16.1 14.6": ["seraph"], "6.8 13.3 -0.3": ["rancorously"], "1.8 4.7 23.5": ["sauterne"], "17.8 11.0 16.1": ["swizz"], "0.2 7.0 13.5": ["jagah"], "8.0 -2.3 4.4": ["joomla"], "18.1 5.9 19.4": ["ukeleles"], "13.7 10.9 7.5": ["comsumers"], "1.2 -5.1 -0.8": ["mecu"], "8.8 11.5 23.4": ["gorget"], "0.6 -10.2 -0.3": ["subdirector"], "-2.6 24.8 3.0": ["anwser"], "8.8 -9.3 12.8": ["nextweek"], "-8.3 20.7 3.8": ["gratefull"], "12.8 17.2 11.4": ["chinar"], "16.3 5.4 21.4": ["pomanders"], "-7.1 6.1 8.8": ["revisional"], "7.2 -7.0 4.9": ["internazionale"], "12.8 10.1 22.1": ["huffin"], "18.8 -6.5 4.1": ["itsfirst"], "-3.2 17.5 18.5": ["virginities"], "24.4 -2.5 -1.3": ["earlierthis"], "-5.4 13.2 -1.0": ["anout"], "15.9 7.3 20.4": ["pierhead"], "-4.1 5.3 0.9": ["microdose"], "0.9 8.0 11.3": ["myotonia"], "10.0 15.3 8.4": ["attocell"], "10.9 11.2 15.8": ["breadths"], "5.3 0.6 17.5": ["huling"], "11.9 1.2 -4.3": ["micropump"], "29.8 5.1 3.0": ["ecorp"], "12.3 24.7 12.4": ["battlewagon"], "10.4 20.1 9.0": ["doesent"], "8.0 10.3 3.7": ["iosis"], "8.0 0.2 4.8": ["policesaid"], "8.1 2.2 5.8": ["specators"], "16.2 -2.5 38.1": ["roughy"], "15.2 8.1 10.8": ["demister"], "8.3 5.6 9.3": ["polie"], "12.0 8.3 2.4": ["webos"], "17.2 4.5 -1.1": ["telelvision"], "14.0 -5.5 12.3": ["profe"], "15.5 10.7 9.9": ["eartquake"], "4.8 3.0 13.7": ["deborah"], "1.8 15.6 8.8": ["irrevelant"], "5.3 16.9 10.4": ["simony"], "12.8 8.6 19.9": ["cryonic"], "-1.8 13.9 1.1": ["unfortuante"], "3.4 10.7 5.7": ["losslessly"], "-2.7 7.7 -0.1": ["uncited"], "15.4 11.1 16.9": ["stunna"], "12.7 5.0 19.4": ["bodysurfed"], "15.2 5.1 2.0": ["definably"], "8.2 0.1 3.3": ["backwages"], "16.5 8.2 20.0": ["chilean"], "1.5 5.3 10.7": ["scudettos"], "-4.2 11.9 5.2": ["plann"], "13.6 17.4 23.5": ["ajumma"], "1.8 20.5 12.3": ["mensches"], "14.1 7.5 29.1": ["crossbill"], "-3.4 -1.9 4.7": ["successsful"], "6.2 14.5 9.4": ["easyto"], "9.1 12.6 17.3": ["liana"], "17.9 24.3 3.1": ["inadvertedly"], "-0.8 4.5 5.1": ["houseparent"], "11.6 2.7 25.2": ["pruney"], "-3.1 5.2 0.2": ["inthese"], "9.3 -1.4 15.4": ["saranno"], "14.4 3.7 26.7": ["reishi"], "16.9 1.4 36.6": ["haupia"], "8.8 24.0 11.9": ["embellisher"], "-8.4 -0.6 0.6": ["columbinus"], "5.7 11.6 2.7": ["placelessness"], "8.8 3.1 20.0": ["snorkling"], "25.3 12.8 21.5": ["sandaled"], "10.9 9.5 15.6": ["habilis"], "1.1 14.3 10.5": ["unsown"], "3.8 12.9 13.0": ["sooooooooooo"], "2.2 2.4 7.2": ["boththe"], "8.9 11.6 9.8": ["squaregaiter"], "12.6 3.0 4.1": ["snazz"], "10.5 21.2 10.0": ["supersonically"], "16.0 5.9 16.6": ["brushers"], "13.4 -1.1 10.9": ["boxload"], "27.0 13.6 23.4": ["splosh"], "11.5 13.4 2.5": ["mounter"], "8.7 18.2 13.4": ["toooooo"], "5.2 17.0 13.9": ["inaccessibly"], "11.8 11.1 13.4": ["losse"], "9.6 1.8 10.6": ["gastroesophageal"], "15.8 5.2 12.3": ["monoliners"], "-2.5 6.6 11.7": ["allowables"], "6.3 3.8 13.1": ["partipants"], "10.5 12.6 15.7": ["thefamily"], "6.8 9.6 19.3": ["grizzles"], "-1.2 5.5 2.0": ["ablum"], "16.5 10.2 26.0": ["hyrax"], "5.9 12.4 -0.0": ["goups"], "4.5 5.3 10.3": ["pancha"], "7.3 8.8 18.0": ["braaing"], "-1.3 3.9 -2.6": ["convicing"], "8.9 15.0 8.4": ["hokiness"], "1.3 -5.5 1.0": ["telecourses"], "3.7 13.4 19.9": ["somites"], "5.8 18.3 15.9": ["lungblower"], "12.2 5.4 44.5": ["meuniere"], "-8.2 27.9 5.4": ["demythologize"], "1.3 10.3 6.0": ["phosphonates"], "13.8 12.1 10.9": ["arcology"], "7.3 23.3 27.8": ["miconia"], "5.5 24.6 1.3": ["falsifier"], "0.8 11.8 5.6": ["frocking"], "7.3 8.9 10.3": ["nger"], "5.8 18.9 11.7": ["paternalists"], "6.0 20.4 2.5": ["engineroom"], "12.1 16.0 24.9": ["tamarisks"], "8.7 18.6 8.8": ["karmabhoomi"], "12.4 -7.1 2.8": ["conract"], "12.1 15.2 11.3": ["untouchably"], "11.5 5.0 14.1": ["huskers"], "1.0 14.8 7.5": ["inkosi"], "10.2 11.0 18.7": ["crosby"], "12.1 4.3 10.0": ["elata"], "9.4 -2.7 2.4": ["deveopment"], "13.0 9.2 10.3": ["stuffiest"], "-4.1 3.2 2.9": ["familles"], "-6.9 -2.8 0.7": ["ncome"], "13.0 13.4 9.0": ["bearhugs"], "14.4 20.6 10.6": ["cultureless"], "10.6 6.4 15.8": ["recipie"], "13.5 8.1 11.2": ["befores"], "21.3 11.0 26.8": ["bellflowers"], "5.8 -3.5 7.3": ["precommissioning"], "4.6 22.4 9.9": ["rankly"], "15.6 6.2 -2.7": ["ticketer"], "2.9 9.5 13.4": ["chromatograph"], "2.6 9.9 4.7": ["quenchers"], "-6.2 4.0 -2.0": ["abl"], "-0.9 6.1 2.5": ["performable"], "21.5 19.7 14.6": ["mousehole"], "-2.6 37.2 4.6": ["dushman"], "14.7 15.9 7.9": ["digeridoo"], "-9.7 4.8 -9.4": ["cousel"], "7.1 17.6 8.8": ["giftees"], "0.5 16.7 8.9": ["ofwhat"], "3.0 10.8 5.5": ["definitized"], "-4.2 1.8 8.4": ["zearalenone"], "-4.2 -3.2 2.8": ["evaulated"], "-2.6 0.7 1.8": ["curacy"], "3.1 8.4 12.2": ["comunidad"], "6.1 18.2 14.7": ["weals"], "-3.6 -1.6 5.6": ["flonase"], "20.6 23.5 13.9": ["insiderism"], "10.7 -8.9 7.7": ["aed"], "4.9 10.7 3.9": ["ights"], "23.1 22.5 20.4": ["manlike"], "3.9 16.3 -1.7": ["skeptism"], "5.2 10.5 8.3": ["pyrometallurgical"], "-1.6 27.4 -0.1": ["seargent"], "10.1 12.1 12.7": ["unbottled"], "6.8 12.6 22.5": ["boga"], "-0.7 -0.6 1.8": ["powerdirector"], "10.6 14.5 11.7": ["hahahahah"], "11.6 5.5 16.6": ["festivus"], "2.4 8.0 17.2": ["monosaccharides"], "9.9 -10.9 2.9": ["accouting"], "8.0 12.5 4.3": ["telegraphist"], "3.7 21.6 2.7": ["infamies"], "2.6 0.2 18.5": ["chari"], "3.1 25.6 5.3": ["hurtfulness"], "14.8 18.6 3.9": ["essentialy"], "12.5 1.9 13.8": ["jewllery"], "9.9 6.7 6.6": ["theone"], "4.2 10.8 6.7": ["tizzies"], "5.3 -2.0 14.4": ["theweek"], "11.4 24.2 6.2": ["metanarrative"], "17.5 16.5 26.8": ["thrip"], "16.3 1.6 20.2": ["coverless"], "2.4 24.1 13.1": ["sidejacking"], "1.3 4.3 17.2": ["volumizer"], "9.6 3.1 3.6": ["shopfitter"], "7.3 3.1 1.7": ["properness"], "9.0 5.5 9.6": ["bienvenue"], "10.7 -7.9 -6.5": ["chrisdanger"], "-0.5 6.0 16.7": ["ryegrasses"], "8.0 -4.2 7.8": ["strs"], "-7.0 -6.0 -2.9": ["neurointerventional"], "1.6 7.4 11.2": ["accha"], "12.7 5.2 10.4": ["wildin"], "16.9 17.8 27.6": ["donks"], "9.6 19.1 12.7": ["vail"], "1.1 20.5 6.9": ["particularist"], "-0.2 8.2 6.4": ["jorge"], "9.7 10.6 4.6": ["outto"], "15.5 -0.1 41.4": ["provencal"], "11.0 17.6 12.9": ["yobbishness"], "2.5 15.3 11.3": ["mvhsbball"], "18.4 11.2 26.9": ["sanger"], "7.6 13.6 13.5": ["scratchily"], "4.0 8.5 20.2": ["chordate"], "1.2 -5.8 10.0": ["emploi"], "-5.2 10.4 2.6": ["roversman"], "8.0 15.4 18.1": ["fosse"], "-1.4 -0.9 9.5": ["viscosupplement"], "1.9 2.1 9.7": ["triacylglycerols"], "7.0 6.0 11.2": ["steerers"], "5.1 4.1 23.5": ["vleis"], "21.0 10.2 9.4": ["clevice"], "0.0 20.3 1.9": ["persepective"], "-2.4 40.2 -3.4": ["mojaheds"], "14.9 2.1 25.9": ["highboys"], "16.3 19.5 3.2": ["ticketers"], "3.9 5.1 6.0": ["puram"], "17.6 2.8 18.0": ["petroluem"], "7.6 26.2 2.7": ["indoctrinations"], "1.7 12.8 15.5": ["mamatay"], "-3.9 -0.1 8.5": ["typicals"], "14.7 11.4 29.1": ["gazania"], "16.5 8.2 23.4": ["saltshakers"], "11.2 16.0 23.6": ["loy"], "6.4 3.6 11.6": ["hypotrichosis"], "16.2 24.8 6.8": ["defacers"], "-0.9 9.0 17.1": ["tronc"], "-3.5 -2.0 1.3": ["pancrelipase"], "3.0 12.3 18.6": ["outbred"], "11.8 6.6 17.8": ["chinatown"], "16.3 17.2 6.7": ["rumormill"], "2.3 8.3 10.8": ["downsampling"], "-4.5 7.9 18.3": ["budgetwise"], "9.1 5.2 12.7": ["interspaced"], "-0.7 7.2 1.6": ["myogenic"], "-4.3 6.5 2.4": ["jexbo"], "-2.1 8.5 5.4": ["seasn"], "5.8 -2.1 7.0": ["binderies"], "2.8 7.1 3.5": ["caretake"], "-0.9 -5.9 6.0": ["organsing"], "8.2 2.3 6.9": ["kero"], "10.0 9.3 15.8": ["hydromulch"], "3.2 13.3 12.3": ["aiight"], "-0.9 34.5 3.6": ["miltants"], "0.9 3.7 0.7": ["delgation"], "12.3 14.0 17.4": ["intot"], "16.4 19.8 1.7": ["urinator"], "8.1 12.1 12.5": ["armco"], "2.0 1.3 5.6": ["lacklusture"], "16.6 3.9 25.4": ["africana"], "1.6 7.5 20.9": ["moreno"], "-0.5 11.8 10.4": ["methylglyoxal"], "8.8 1.2 7.4": ["unpatterned"], "8.5 9.9 11.9": ["sandtraps"], "21.4 1.6 8.0": ["attr"], "2.5 0.7 7.6": ["dhb"], "-3.5 14.1 14.5": ["hdcp"], "-10.9 12.4 5.3": ["abruption"], "8.7 3.7 8.4": ["funiculars"], "-6.0 -4.3 13.2": ["nasabing"], "4.0 7.6 27.8": ["forb"], "1.0 19.3 11.4": ["doonga"], "9.6 10.7 -2.0": ["nev"], "1.1 9.5 6.5": ["dirgelike"], "1.4 14.9 5.9": ["juxtapositioning"], "3.5 8.1 8.7": ["droits"], "12.2 15.8 10.4": ["whitefella"], "25.4 5.9 7.7": ["bigname"], "3.1 4.8 21.3": ["minivacation"], "-8.7 -0.4 5.6": ["pport"], "-5.1 7.6 6.0": ["backcourtmate"], "4.4 -0.6 11.7": ["powdercoat"], "15.1 13.4 28.3": ["nautically"], "8.2 4.2 5.7": ["biblio"], "7.0 14.7 12.6": ["kneeldown"], "8.4 22.0 10.4": ["scarface"], "8.5 3.3 45.9": ["rillette"], "7.9 -8.2 3.3": ["miliion"], "5.7 5.7 3.2": ["craniomaxillofacial"], "11.7 14.9 6.0": ["embarrasingly"], "8.8 17.5 17.9": ["laforin"], "10.2 -0.7 0.9": ["anddistribution"], "-4.2 -1.4 1.0": ["bioinformatician"], "7.3 10.3 11.5": ["cybrids"], "-2.2 -2.5 -2.2": ["willhelp"], "4.8 11.7 10.8": ["multipartite"], "5.0 3.4 9.5": ["homeseekers"], "4.5 17.3 9.2": ["sensorium"], "11.9 -1.6 3.3": ["entrepeneurship"], "9.0 24.5 3.7": ["erradicate"], "3.1 13.3 17.7": ["sympton"], "5.8 4.0 15.8": ["danza"], "10.8 8.8 4.0": ["microsurgeons"], "14.2 18.4 12.3": ["tokamaks"], "-6.2 12.5 7.8": ["sidebranch"], "6.6 1.4 4.5": ["handprinted"], "0.3 5.8 14.4": ["stacey"], "8.0 15.2 4.4": ["dominent"], "21.8 21.6 12.3": ["earthwards"], "14.3 1.7 8.7": ["chillum"], "5.2 11.5 17.1": ["maut"], "3.6 17.9 15.3": ["personnaly"], "17.8 6.4 12.3": ["panpipe"], "4.2 2.0 0.7": ["recod"], "19.1 -1.6 7.4": ["multinetwork"], "6.6 18.3 8.8": ["recreators", "zonally"], "18.4 7.7 3.6": ["smarphone"], "6.4 22.5 9.4": ["reifying"], "0.5 29.1 2.1": ["missileers"], "6.9 9.1 5.8": ["megaclub"], "5.0 10.8 2.6": ["weblogger"], "12.8 18.5 9.0": ["dieties"], "5.4 9.1 20.9": ["preadolescence"], "15.9 10.2 2.0": ["bandura"], "5.8 11.2 9.9": ["deglobalization"], "6.3 21.0 1.0": ["unmistakenly"], "2.8 26.4 16.3": ["overthinks"], "0.3 13.5 6.6": ["sente"], "2.4 16.5 6.5": ["jipped"], "7.5 23.4 4.8": ["netherland"], "2.5 2.4 -0.2": ["enthesitis"], "5.6 1.8 9.8": ["bifidus"], "-3.5 1.2 2.3": ["herniations"], "11.4 10.0 13.4": ["myo"], "17.7 5.4 45.3": ["freelined"], "-4.1 -3.4 1.6": ["ssc"], "15.4 17.4 6.6": ["wrongest"], "9.8 26.7 1.0": ["reconnoitring"], "7.7 -0.9 4.6": ["fischer"], "2.1 12.4 9.0": ["cros"], "-7.5 2.6 4.9": ["hypersecretion"], "2.4 -0.2 10.5": ["intercalary"], "0.8 16.1 8.9": ["offtopic"], "1.8 13.7 12.6": ["yud"], "5.8 2.7 9.2": ["highter"], "15.7 8.6 0.4": ["overengineered"], "-6.6 20.1 1.5": ["universalists"], "-0.1 11.6 10.1": ["crackhouses"], "-7.1 24.6 -2.4": ["guiltiness"], "18.5 1.5 24.8": ["superliners"], "20.4 4.8 21.2": ["suspendered"], "3.2 12.2 8.1": ["fides"], "-0.6 6.4 -1.0": ["dasa"], "17.9 3.6 37.0": ["fritos"], "9.7 24.4 3.5": ["fores"], "-3.2 -1.6 6.8": ["electrologists"], "8.6 13.2 5.2": ["ambisexual"], "12.1 6.0 12.0": ["protheses"], "1.8 11.7 5.8": ["overactivated"], "14.8 6.3 20.5": ["slurried"], "2.7 15.3 19.5": ["leafspot"], "-0.3 7.7 6.3": ["quartos"], "14.2 7.6 8.8": ["businessses"], "6.0 2.2 9.9": ["precamp"], "11.5 16.1 4.0": ["ecrime"], "11.5 24.3 12.3": ["cumbersomely"], "3.0 8.9 16.4": ["nutriment"], "-0.1 18.4 9.3": ["sonship"], "9.0 -8.4 5.4": ["offest"], "-1.8 -0.7 4.4": ["malunion"], "-4.7 6.5 8.4": ["yol"], "6.9 9.4 6.3": ["soberest"], "29.3 9.0 12.1": ["carboard"], "-5.8 -0.7 7.0": ["kyoung"], "-3.7 4.6 13.0": ["bulbar"], "20.1 5.8 11.9": ["kamishibai"], "10.9 7.5 19.3": ["insteps"], "8.0 6.0 10.4": ["seob"], "15.7 21.8 9.9": ["inertly"], "9.4 -0.8 5.5": ["dowdier"], "1.7 2.1 8.7": ["naco"], "13.3 6.1 11.9": ["naomi"], "16.0 7.2 33.2": ["gula"], "9.9 5.1 13.1": ["huntaway"], "3.8 9.1 13.5": ["grouchier"], "6.8 19.8 4.4": ["promulgator"], "3.8 18.4 17.4": ["kangri"], "-1.3 4.3 17.5": ["realgar"], "8.1 20.6 0.3": ["accustoming"], "4.5 7.6 9.4": ["prweb"], "3.1 2.8 3.7": ["pursers"], "6.4 11.7 10.2": ["pollarded"], "0.9 3.1 2.1": ["focuss"], "11.6 7.4 1.8": ["polariser"], "-0.2 9.4 3.2": ["histocompatibility"], "14.0 16.7 6.8": ["roadworker"], "-0.9 3.8 4.2": ["wellsites"], "-2.4 12.9 10.8": ["subclause"], "6.8 27.7 -3.4": ["forment"], "-7.3 3.7 -0.4": ["entlang"], "-2.4 6.3 7.2": ["archakas"], "19.5 12.7 17.1": ["gridwork"], "6.7 9.2 8.5": ["afirst"], "5.8 9.6 7.1": ["populariser"], "-1.2 16.5 -2.5": ["introspected"], "7.3 7.2 21.7": ["drysuits"], "12.9 10.1 9.4": ["overtraded"], "10.2 17.1 18.2": ["polleros"], "6.5 11.8 17.2": ["dali"], "7.5 -13.0 3.4": ["allpay"], "16.8 7.7 37.7": ["bolina"], "-2.7 -3.7 6.0": ["daughtercards"], "-3.9 28.6 9.0": ["opponenets"], "10.5 3.5 13.1": ["holdiay"], "21.6 0.6 29.0": ["panacotta"], "-0.8 3.4 6.4": ["studens"], "6.3 14.1 8.2": ["bidoons"], "13.4 5.2 9.6": ["sociedad"], "5.4 4.8 11.8": ["shorttrack", "watsu"], "7.9 8.9 9.4": ["repl"], "12.7 3.8 3.6": ["rangehood"], "11.2 7.9 25.1": ["shorthairs"], "5.2 4.9 2.9": ["drugless"], "0.0 12.0 13.1": ["juuuuust"], "5.5 23.1 7.5": ["outwrestling"], "9.2 16.1 18.3": ["windiness"], "-5.0 14.4 1.5": ["surpirse"], "11.6 14.1 5.7": ["battlin"], "3.7 8.5 5.9": ["mineability"], "4.4 9.0 12.9": ["westbrook"], "5.4 2.0 7.2": ["barbituates"], "6.5 12.7 17.1": ["levigated"], "3.1 10.9 8.5": ["linearisation"], "28.1 3.7 11.1": ["telcommunications"], "-0.3 7.9 10.2": ["administrasyon"], "6.6 3.0 6.8": ["alleen"], "13.8 5.4 7.9": ["archaeo"], "5.2 14.2 14.7": ["askagain"], "15.6 2.0 28.3": ["gigger"], "6.3 7.1 7.2": ["baminercept"], "6.6 -4.4 6.8": ["bem"], "-0.3 6.8 20.5": ["bodysurfers"], "0.3 7.7 16.9": ["cryoprotectants"], "3.2 12.2 4.0": ["seeable"], "-1.4 16.4 11.4": ["vasu"], "3.3 7.9 0.6": ["abuja"], "4.6 7.0 17.2": ["gastos"], "-0.2 5.2 15.9": ["katawan"], "14.1 5.8 10.3": ["verschillende"], "-2.5 7.8 4.1": ["ahad"], "2.0 9.9 11.1": ["kesa"], "-3.4 4.7 -4.0": ["includeing"], "2.8 3.7 10.4": ["commonhold"], "22.3 -3.8 16.0": ["superport"], "0.2 10.9 9.2": ["tumhare"], "18.3 7.1 28.1": ["loropetalum"], "4.0 7.0 6.4": ["vad"], "4.6 12.5 7.7": ["underware"], "7.7 3.6 6.4": ["quoad"], "3.5 9.4 6.5": ["artappraiser"], "-0.3 4.6 5.9": ["psec"], "16.7 4.2 8.7": ["swanking"], "8.7 7.7 14.3": ["reminbi"], "4.7 -2.5 16.0": ["safefood"], "8.8 0.7 12.2": ["jordans"], "6.5 12.5 9.9": ["laught"], "-1.3 0.0 7.5": ["apoyo"], "5.4 27.2 7.3": ["outwilled"], "3.8 11.2 12.1": ["mucormycosis"], "4.0 20.0 14.7": ["aseismic"], "6.7 11.4 7.1": ["recentered"], "8.9 19.0 17.5": ["ibexes"], "8.6 12.9 10.7": ["weirdnesses"], "10.6 12.4 15.0": ["handguard"], "16.8 17.1 10.9": ["undesigned"], "-3.3 7.6 4.0": ["expositors"], "18.6 6.4 42.7": ["goldeye"], "9.1 7.7 10.2": ["uninstallers"], "3.0 13.7 7.7": ["similars"], "0.7 26.5 7.8": ["gadol"], "12.2 17.1 9.7": ["jeeploads"], "13.7 4.5 18.2": ["snooki"], "7.6 0.5 16.0": ["foodstall"], "4.5 2.4 0.6": ["marchpast"], "11.7 -1.1 1.5": ["reupping"], "5.2 -1.6 12.2": ["viernes"], "10.6 8.6 31.7": ["unmolding"], "7.4 10.9 13.7": ["cravin"], "15.2 19.3 26.2": ["heffalump"], "15.0 5.8 26.3": ["carex"], "5.2 -8.8 8.9": ["oping"], "7.7 9.3 33.3": ["tricos"], "11.2 0.5 -1.8": ["inititally"], "13.5 11.3 6.2": ["unassuaged"], "2.8 -5.5 6.8": ["underfilled"], "-0.1 -2.4 31.8": ["spiedie"], "8.3 4.3 9.7": ["watc"], "-2.7 18.1 0.6": ["outburts"], "1.2 12.2 6.9": ["thermographer"], "-1.6 10.8 10.2": ["pecentage"], "5.4 19.5 10.2": ["scalpings"], "-3.9 5.2 8.5": ["landlording"], "10.1 7.4 3.8": ["tubelight"], "-1.1 1.3 20.2": ["eksena"], "7.7 -2.2 10.3": ["extortionately"], "5.5 7.8 14.6": ["intergender"], "6.6 15.8 18.7": ["overbrowsing"], "2.1 10.3 4.5": ["polypyrrole"], "20.5 18.8 22.1": ["picador"], "10.3 6.8 10.7": ["miserabilism"], "6.8 -2.3 1.6": ["nanoclay"], "3.9 21.4 13.1": ["spoilerific"], "6.0 0.5 5.2": ["solidwaste"], "13.2 7.0 19.5": ["sediba"], "13.4 11.6 21.9": ["braw"], "11.4 17.0 6.6": ["phlogiston"], "6.9 6.1 4.4": ["bisher"], "11.7 7.1 8.6": ["jazzily"], "11.4 18.8 2.4": ["jailbreaked"], "18.3 -6.6 24.4": ["basketweave"], "8.6 10.6 16.8": ["broadleaved"], "10.3 13.7 20.8": ["jibber"], "12.0 8.8 17.5": ["kulhars"], "3.8 -1.1 7.7": ["setaside"], "-0.5 18.0 2.6": ["angularities"], "4.4 3.1 -2.5": ["recuses"], "11.2 9.4 10.5": ["hyperrealist"], "-4.2 2.5 0.7": ["dialyzed"], "8.3 17.8 12.7": ["transfigures"], "5.8 14.8 9.1": ["mns"], "-6.4 6.7 10.9": ["chane"], "13.6 13.3 11.9": ["sandles"], "-5.8 15.7 7.5": ["abstinance"], "11.3 14.4 18.8": ["mariah"], "-3.5 5.7 17.8": ["tanong"], "12.7 7.2 15.3": ["shway"], "1.8 -3.0 3.7": ["appelate"], "-1.1 6.5 15.4": ["downbound"], "-1.0 13.6 6.9": ["travell"], "1.6 7.3 9.8": ["fludrocortisone"], "6.9 8.8 11.2": ["hights"], "6.7 20.9 2.8": ["lacky"], "2.7 20.9 10.8": ["twinship"], "17.0 18.3 7.1": ["mindshift"], "2.6 19.7 27.7": ["dewclaws"], "-1.7 10.1 24.6": ["junmai"], "2.2 3.5 4.3": ["universites"], "19.6 -2.6 -6.2": ["acquision"], "10.5 9.5 13.5": ["evidentally"], "3.4 -2.5 10.0": ["ganar"], "8.8 9.7 -4.6": ["hindustan"], "13.0 4.5 19.7": ["kwitis"], "10.1 14.5 9.5": ["sextile"], "-2.1 3.7 8.8": ["periventricular"], "13.9 34.7 10.1": ["destroyable"], "0.3 17.2 16.1": ["guttiest"], "18.0 21.1 28.9": ["fiddlesticks"], "7.7 17.5 20.8": ["fifthly"], "6.7 20.1 13.3": ["tebuthiuron"], "7.4 2.8 17.9": ["elin"], "1.2 5.1 13.9": ["gts"], "6.1 8.8 20.5": ["ryder"], "14.2 12.9 7.0": ["joystiq"], "5.0 -0.6 8.2": ["ufficiale"], "7.8 25.8 20.5": ["sealanes"], "-2.0 17.9 20.5": ["amae"], "4.8 15.4 4.2": ["minsiters"], "2.3 17.3 11.0": ["uppercutting"], "-7.7 5.7 2.7": ["samvat"], "13.4 13.3 14.8": ["lols"], "19.0 10.3 -5.3": ["satelitte"], "18.1 10.4 22.7": ["billycart"], "15.3 3.7 18.4": ["bip"], "17.2 17.4 14.4": ["screechers"], "19.7 4.7 6.5": ["tronica"], "13.1 23.4 6.6": ["narcisstic"], "10.5 12.3 41.1": ["muttons"], "7.5 -3.1 1.6": ["maketing"], "3.5 4.2 8.1": ["parametrically"], "6.4 10.6 7.3": ["automony"], "-1.8 1.3 13.6": ["cita"], "14.5 18.2 10.7": ["tmu"], "9.6 11.6 7.8": ["chattery"], "6.7 10.5 2.0": ["alse"], "0.6 12.7 19.1": ["transhumance"], "4.3 10.5 28.5": ["crucifers"], "6.9 5.2 2.3": ["retuns"], "26.1 17.2 45.9": ["mudbug"], "-1.6 -0.2 7.7": ["interprovincials"], "6.1 6.9 23.3": ["maas"], "14.3 15.3 20.7": ["armlet"], "4.3 1.1 13.5": ["mota"], "10.2 9.8 8.7": ["unfundable"], "2.9 0.0 13.1": ["comedia"], "10.8 8.8 19.3": ["fada"], "19.3 -0.8 -7.5": ["andentertainment"], "11.6 2.9 7.7": ["metacrawlers"], "-9.8 6.9 2.0": ["saaid"], "-0.3 18.3 1.0": ["adab"], "8.9 13.8 8.0": ["legalizers"], "12.3 9.1 12.9": ["fingerpaints"], "3.0 8.9 11.0": ["thebaine"], "12.7 -0.7 2.9": ["bioelectronics"], "-0.1 -0.8 4.1": ["prorations"], "4.2 4.0 11.0": ["gha"], "18.0 0.6 6.1": ["skidmark"], "8.5 18.1 10.2": ["inthat"], "4.4 9.9 3.3": ["msot"], "2.9 21.9 -2.2": ["misportrayed"], "6.5 11.7 7.7": ["prerolls"], "7.2 7.8 7.7": ["protrusive"], "6.1 2.2 12.9": ["comprable"], "-1.7 7.7 20.4": ["grigio"], "13.0 10.4 -1.4": ["soullessly"], "9.3 1.8 -1.6": ["perfumier"], "5.0 10.5 8.5": ["orates"], "12.8 24.8 15.4": ["airbender"], "8.9 8.9 6.5": ["financialinstitutions"], "2.6 -3.9 14.9": ["sito"], "23.6 13.8 16.9": ["tipsily"], "7.9 20.2 9.3": ["denudes"], "11.8 -7.7 6.5": ["mediumsized"], "5.6 27.5 7.9": ["manuver"], "4.4 11.1 7.2": ["curanderas"], "9.0 5.7 41.4": ["grillades"], "10.2 8.9 10.9": ["aitch"], "5.5 39.9 12.5": ["warbloggers"], "-2.6 8.2 -1.3": ["edy"], "10.1 -3.4 30.4": ["farofa"], "19.7 2.7 15.4": ["heavyduty"], "11.4 1.0 12.9": ["cavaquinho"], "5.3 0.2 13.2": ["yearover"], "7.9 13.2 14.3": ["datagrams"], "17.1 15.5 10.7": ["stoled"], "2.3 3.5 -2.0": ["retrenchees"], "4.0 17.1 5.6": ["imagin"], "2.6 5.5 5.4": ["recoved"], "-1.0 11.9 7.5": ["ephebophilia"], "-0.2 14.1 8.8": ["situaiton"], "6.7 10.8 18.5": ["sylvia"], "8.7 11.5 15.8": ["dof"], "0.2 8.8 8.6": ["postflight"], "-2.0 9.2 8.2": ["concelebrant"], "7.0 32.0 3.7": ["afganistan"], "-2.5 27.4 10.6": ["ignorances"], "-7.5 5.9 -0.0": ["centredness"], "22.2 13.3 12.2": ["doggles"], "2.1 9.0 19.2": ["biktima"], "4.0 11.2 9.8": ["leats"], "6.9 12.0 -2.1": ["proselytiser"], "15.5 6.7 18.9": ["mixin"], "-4.2 14.2 3.6": ["acquaintence"], "-5.4 1.6 6.1": ["sible"], "3.5 7.4 10.2": ["collec"], "-7.3 17.7 3.4": ["deviances"], "-2.9 -3.1 6.7": ["daycamp"], "7.8 5.3 10.8": ["makeit"], "14.6 7.6 27.5": ["nepeta"], "1.0 1.7 9.9": ["sodic"], "0.7 11.7 13.2": ["kup"], "10.3 2.8 14.2": ["dozenth"], "7.3 6.5 9.6": ["torneo"], "10.7 -1.1 14.1": ["sportsters"], "-2.6 11.1 7.3": ["macadamized"], "9.6 9.1 7.1": ["cbd"], "11.9 17.6 3.8": ["grabing"], "13.8 1.3 7.8": ["yello"], "-1.8 21.4 1.6": ["cajoler"], "2.0 2.1 10.7": ["octyl"], "5.3 -3.0 10.7": ["ivf"], "-3.3 5.4 14.2": ["pylorus"], "21.9 9.8 5.7": ["outmatching"], "12.6 13.9 5.7": ["transliterating"], "13.8 10.5 21.5": ["counterperson"], "-4.0 21.9 4.8": ["relativized"], "-6.1 11.3 -4.0": ["webelieve"], "-5.0 12.1 5.6": ["decesion"], "5.2 9.8 18.6": ["spinto"], "10.7 17.9 19.1": ["muthafuckas"], "0.0 9.9 5.8": ["gme"], "4.5 13.7 15.5": ["sair"], "9.0 5.3 28.4": ["fieldfares"], "1.2 17.3 3.2": ["preception"], "13.7 11.3 8.6": ["cleancut"], "3.2 17.6 8.3": ["shipmasters"], "10.2 19.6 22.1": ["willya"], "10.7 10.7 7.2": ["deperately"], "5.5 5.9 12.6": ["thursdays"], "8.8 7.3 9.8": ["misgauged"], "9.3 21.4 8.3": ["ominousness"], "10.8 7.5 12.1": ["thomassondan"], "0.2 -0.8 13.8": ["natinal"], "12.9 -4.7 10.6": ["nuova"], "15.5 -6.1 2.4": ["ndustry"], "9.6 18.4 8.6": ["heterophobic"], "-1.5 7.2 24.1": ["apiculturist"], "16.5 10.7 9.4": ["rackable"], "4.5 10.2 1.5": ["shilanyas"], "2.6 1.0 5.3": ["lundi"], "2.3 25.7 7.3": ["tentmate"], "17.3 11.2 13.2": ["ahhhhhh"], "6.8 21.3 24.4": ["broadleaves"], "3.9 13.1 2.8": ["somany"], "21.8 8.0 22.5": ["snakeskins"], "5.6 4.1 14.2": ["bowie"], "14.1 21.7 14.6": ["povo"], "14.0 14.4 4.4": ["swype"], "7.1 16.1 6.3": ["aerosolize"], "22.2 5.8 21.8": ["bitsy"], "5.0 11.7 8.3": ["outfinishing"], "3.2 5.7 11.2": ["gettogether"], "10.7 15.2 9.6": ["ponycar"], "7.9 22.0 12.1": ["misclubbed"], "9.4 17.5 34.6": ["rotifer"], "11.1 1.4 -3.2": ["valueof"], "8.7 2.2 20.6": ["vernix"], "16.9 28.5 12.7": ["gorund"], "3.1 15.7 17.9": ["stepdads"], "-0.3 26.7 -1.2": ["innoncent"], "2.8 6.0 -1.3": ["lte"], "-0.5 1.7 12.6": ["factorsthat"], "11.3 15.4 21.4": ["haunter"], "0.6 9.5 10.5": ["ramesh"], "10.6 2.3 11.7": ["pulpmill"], "7.3 4.9 1.7": ["anencephalic"], "20.4 14.9 15.0": ["repeller"], "-5.8 -3.9 4.7": ["millidarcies"], "22.4 11.4 18.3": ["wacks"], "-1.4 12.3 -2.5": ["opinionmakers"], "7.9 9.0 24.7": ["gooier"], "5.4 10.0 0.2": ["clubsides"], "-6.1 -2.7 5.3": ["vinflunine"], "1.4 6.6 5.3": ["rebreathing"], "9.0 -2.1 14.1": ["rubboard"], "-0.7 13.3 16.4": ["emm"], "0.6 -3.5 7.4": ["emplo"], "-10.7 7.0 -1.3": ["anthologised"], "23.8 -3.2 13.8": ["displayers"], "0.0 15.2 4.6": ["sermonise"], "3.5 7.9 2.5": ["benifited"], "12.3 5.5 6.5": ["nichey"], "22.3 13.2 1.7": ["innerworkings"], "-0.4 7.3 15.9": ["proyekto"], "12.0 6.6 7.8": ["unmissed"], "22.8 3.1 8.6": ["beermats"], "-2.7 15.4 6.2": ["unascertainable"], "5.2 5.5 10.9": ["ayran"], "18.3 17.9 9.1": ["eliptical"], "20.2 11.3 16.2": ["mosiac"], "20.8 16.6 15.9": ["morasses"], "-1.6 4.9 11.7": ["metaplasia"], "10.0 5.7 11.0": ["lighweight"], "15.9 24.8 6.5": ["sexbot"], "14.7 13.5 15.2": ["gobful"], "-4.0 18.5 10.3": ["situaton"], "4.0 -1.8 21.1": ["playdays"], "4.0 30.1 15.4": ["villans"], "3.4 22.2 4.1": ["perservering"], "1.7 0.2 11.5": ["hydroplant"], "-5.9 9.2 -1.3": ["imputable"], "10.6 28.0 10.3": ["diabolism"], "14.2 0.0 8.5": ["ashare"], "21.9 14.2 15.2": ["flyswatters"], "18.6 18.2 20.5": ["churnings"], "5.4 19.3 -0.2": ["mindreading"], "7.2 25.9 5.8": ["blackshirt"], "6.1 10.0 6.0": ["seniorless"], "11.1 -3.7 22.2": ["pubby"], "17.6 10.8 5.0": ["trailblaze"], "14.0 22.6 12.8": ["flashovers"], "4.0 1.5 -1.7": ["caried"], "4.1 14.5 5.2": ["govermnent"], "3.3 10.3 4.9": ["hleb"], "-1.9 4.8 11.1": ["grantwriting"], "2.7 19.3 5.8": ["unnuanced"], "2.0 7.8 12.7": ["contractive"], "4.1 -0.3 8.3": ["insa"], "1.0 4.9 -0.9": ["acadesine"], "11.0 19.4 9.7": ["outand"], "21.2 14.2 13.3": ["shrek"], "1.5 15.4 2.2": ["gve"], "19.7 10.8 24.7": ["gelid"], "17.0 -2.4 11.0": ["spoolbase"], "-4.6 8.6 15.2": ["cohabiters"], "3.0 2.3 6.3": ["nonavailability"], "8.7 15.7 7.3": ["metronomically"], "11.8 19.7 12.5": ["sitteth"], "3.4 13.9 18.0": ["sakta"], "10.2 1.4 7.3": ["quinapril"], "-7.8 9.3 2.1": ["disentitled"], "11.6 1.3 0.1": ["opco"], "3.7 8.3 13.7": ["buppies"], "13.3 21.5 16.2": ["freaken"], "10.1 9.0 2.9": ["bolometer"], "8.9 9.1 16.3": ["overtightening"], "0.7 2.8 10.2": ["transrectal"], "9.8 20.4 14.8": ["unchivalrous"], "-6.4 -5.8 6.7": ["weatherizes"], "0.7 22.9 13.8": ["becauseit"], "15.2 13.1 13.4": ["likethe"], "-3.6 7.5 18.2": ["shorelands"], "7.9 16.3 12.2": ["nisha"], "-7.4 11.5 6.9": ["butthey"], "17.7 21.2 14.5": ["clobberin"], "-5.2 2.0 15.1": ["presweetened"], "6.4 7.9 8.2": ["travelog"], "4.3 6.8 2.5": ["seeed"], "18.3 9.3 37.9": ["splitshot"], "13.8 6.2 9.9": ["crackerbox"], "1.3 16.7 2.5": ["excuted"], "-5.9 11.1 11.9": ["sestina"], "6.4 7.2 2.8": ["exacly"], "21.7 6.7 9.9": ["vrooms"], "7.4 1.4 12.9": ["daming"], "6.8 3.0 3.6": ["stampa"], "4.2 39.3 12.0": ["spellcaster"], "15.7 11.2 5.7": ["superheavy"], "7.0 9.0 11.2": ["sanford"], "14.8 1.2 -3.4": ["brightsolid"], "7.0 11.7 23.0": ["weedier"], "9.1 8.6 2.4": ["garmin"], "-3.2 9.3 5.5": ["dijiye"], "19.6 3.4 22.3": ["miraculin"], "1.3 17.6 13.0": ["curfewed"], "7.2 9.0 17.8": ["retagged"], "-1.0 3.6 7.4": ["fibrocartilage"], "13.0 12.2 11.2": ["pinacle"], "18.3 0.8 18.0": ["pigpens"], "16.4 25.8 10.3": ["botmasters"], "1.5 -5.1 1.0": ["accoun"], "4.0 4.8 8.8": ["admittees"], "16.2 9.0 23.6": ["rerolling"], "8.1 16.1 11.2": ["unscare"], "10.5 15.5 30.5": ["ailanthus"], "16.2 13.1 -1.9": ["elsehwere"], "11.9 7.6 16.1": ["chasubles"], "7.4 2.0 8.5": ["veterinaries"], "-6.0 16.4 4.9": ["noninflammatory"], "15.9 -0.7 25.2": ["charbroiler"], "15.3 4.7 21.2": ["guiness"], "7.9 20.3 11.6": ["netstat"], "6.9 4.7 1.1": ["backdates"], "2.7 -3.0 5.7": ["yna"], "9.8 5.1 4.8": ["ebizframe"], "13.9 2.0 8.4": ["wasalso"], "16.3 4.9 34.4": ["tamago"], "6.2 19.1 4.7": ["irreversable"], "14.7 9.4 8.2": ["flatirons"], "7.2 17.1 10.6": ["safecrackers"], "13.3 12.9 16.0": ["beardies"], "6.9 0.6 -2.7": ["promotionals"], "10.5 8.8 31.0": ["lauan"], "7.0 11.3 6.7": ["thermomechanical"], "9.7 3.5 -8.9": ["mlc"], "9.8 8.1 19.0": ["agra"], "10.7 19.2 8.7": ["hastier"], "8.0 3.2 3.1": ["empoyees"], "15.9 7.7 20.9": ["lyra"], "7.4 -3.8 -1.4": ["gestrinone"], "-2.9 5.9 2.2": ["deinstitutionalisation"], "15.7 8.9 7.2": ["effusing"], "13.1 5.5 20.5": ["snakeroot"], "9.2 13.0 15.6": ["klotho"], "12.4 7.8 -2.9": ["develped"], "3.7 27.0 12.0": ["outsiderness"], "0.2 -0.8 18.0": ["raman"], "18.7 -8.3 1.4": ["devicemaker"], "5.7 7.0 13.1": ["exocrine"], "15.9 8.2 11.4": ["deskbar"], "2.3 11.4 10.5": ["cognomen"], "15.8 6.0 4.6": ["democratises"], "5.4 4.4 19.0": ["litterbins"], "2.2 1.7 9.5": ["cdt"], "20.3 2.6 23.8": ["cabers"], "3.8 16.1 15.8": ["countryboy"], "5.9 3.3 12.9": ["inated"], "13.3 2.2 24.3": ["vetkoek"], "10.1 18.3 15.3": ["monarchal"], "9.0 13.2 3.3": ["cdr"], "18.6 8.5 35.3": ["snuffbox"], "4.4 11.0 13.3": ["getto"], "14.8 8.6 12.0": ["unpeeling"], "6.9 1.5 9.6": ["tripeptide"], "0.0 5.1 4.9": ["heer"], "6.2 12.3 3.8": ["heigh"], "6.4 -1.8 -4.7": ["vouchering"], "6.8 2.6 9.9": ["monoglycerides"], "16.6 19.1 18.0": ["mindbogglingly"], "1.5 28.2 6.0": ["paranoic"], "9.4 4.4 13.9": ["yentas"], "18.6 9.3 31.2": ["redbug"], "15.2 20.8 11.6": ["scummiest"], "-4.2 8.8 1.6": ["andwith"], "6.3 21.9 10.0": ["mulla"], "19.7 9.4 21.9": ["mulchers"], "12.9 17.4 13.6": ["sparklines"], "0.8 11.1 5.6": ["bunkrooms"], "12.4 -0.1 5.9": ["indust"], "-2.7 3.9 2.8": ["journalized"], "3.2 15.2 11.9": ["scudetti"], "16.7 2.5 12.2": ["stap"], "2.4 8.3 1.0": ["recuits"], "26.4 15.6 18.9": ["mouselike"], "8.2 12.1 15.0": ["inflammables"], "-3.5 4.9 16.4": ["shootfest"], "3.4 -1.5 -12.5": ["beyerdynamic"], "15.6 14.4 16.4": ["beatboxes"], "12.8 8.2 12.0": ["cetera"], "0.4 6.8 5.3": ["dafx"], "18.5 6.5 3.7": ["mousemats"], "12.4 -1.7 9.3": ["threadless"], "4.4 5.5 4.4": ["tetragonal"], "6.3 7.9 8.1": ["daydreamy"], "9.4 2.5 11.1": ["levys"], "6.6 3.8 -3.8": ["fomerly"], "1.9 4.2 6.2": ["homeworks"], "4.4 9.5 7.0": ["havenot"], "7.6 18.4 17.0": ["bookman"], "20.6 3.5 15.6": ["seedcorn"], "0.7 6.8 11.2": ["desmond"], "-3.4 7.9 -0.7": ["calldown"], "2.9 16.1 10.5": ["immediatedly"], "6.3 15.0 10.2": ["countrymade"], "7.8 15.0 21.8": ["biathalon"], "-5.7 1.5 -2.2": ["iodixanol"], "12.0 7.2 7.7": ["sportscenter"], "17.5 10.5 27.4": ["tinikling"], "10.2 6.7 10.1": ["gentlemans"], "18.6 3.0 20.4": ["trashbag"], "11.4 3.9 6.4": ["infrustructure"], "5.9 3.1 2.4": ["inclding"], "-1.8 11.0 -4.8": ["premising"], "3.8 16.3 4.8": ["stereopsis"], "2.8 4.8 26.1": ["dhania"], "4.3 17.5 12.4": ["nearthe"], "4.1 22.2 13.7": ["reckoner"], "10.2 2.2 26.2": ["bubinga"], "6.8 22.3 15.6": ["lycan"], "7.7 8.7 22.7": ["aviculturist"], "0.5 3.7 14.8": ["bulbing"], "-5.3 20.7 2.6": ["taqlid"], "13.3 4.6 14.5": ["housewifely"], "3.9 5.4 16.6": ["thermowell"], "19.9 8.3 18.7": ["candyman"], "7.1 6.4 6.9": ["clemson"], "1.3 3.3 2.9": ["elicted"], "8.9 25.5 10.2": ["skedaddling"], "6.2 29.4 14.1": ["shinigami"], "0.7 15.3 18.4": ["erysipelas"], "7.3 4.9 5.8": ["semiconductive"], "-3.0 13.8 11.0": ["nifurtimox"], "15.0 6.1 4.1": ["microbatteries"], "2.3 25.4 2.7": ["resitance"], "7.4 14.2 9.7": ["evr"], "13.1 4.2 4.5": ["traget"], "5.2 6.6 7.5": ["forclosed"], "2.9 -0.4 -0.4": ["empl"], "5.0 -3.2 -1.7": ["perfoms"], "-2.2 7.3 4.5": ["pujaris"], "12.7 -6.3 17.0": ["pouffed"], "3.3 13.7 10.4": ["kindreds"], "9.0 17.7 2.2": ["unintellectual"], "1.4 21.0 -3.7": ["wernt"], "5.8 16.1 6.7": ["superlenses"], "2.9 16.0 3.6": ["portayed"], "24.1 14.2 22.6": ["navvy"], "-1.9 17.4 11.9": ["slyer"], "3.3 12.4 9.0": ["advanatage"], "0.4 18.6 7.6": ["johnmarelius"], "9.3 21.6 14.1": ["powerleveling"], "2.9 11.1 3.7": ["delayering"], "0.4 15.3 10.2": ["innocense"], "21.1 1.4 0.3": ["brandmark"], "8.0 9.8 14.9": ["hollower"], "10.4 6.7 14.1": ["tradeables"], "7.9 5.4 17.8": ["carbendazim"], "15.7 16.3 14.6": ["millimetric"], "19.5 8.4 26.3": ["noshers"], "5.5 3.0 -1.4": ["offshorable"], "-6.1 10.5 6.5": ["senority"], "13.1 2.8 20.1": ["photomicrograph"], "13.6 10.1 9.6": ["queening"], "5.1 7.5 8.0": ["tebow"], "1.5 20.9 7.2": ["misbelief"], "13.1 11.4 10.3": ["intermittence"], "6.8 4.9 10.3": ["dant"], "2.7 15.5 15.5": ["deff"], "-3.9 15.3 9.7": ["havenots"], "9.0 10.3 10.2": ["regifter"], "-0.2 9.5 5.2": ["tecnico"], "-8.6 4.6 6.7": ["crossfades"], "4.5 7.0 3.8": ["ranson"], "-0.6 3.0 8.6": ["interdigitated"], "-3.2 3.2 2.9": ["immunotoxicity"], "-1.8 -12.4 10.4": ["acad"], "6.8 12.1 3.4": ["sigificant"], "14.2 8.8 26.6": ["palmate"], "3.6 11.3 11.2": ["pikin"], "10.2 0.3 1.7": ["iodinated"], "-7.2 12.8 3.5": ["yahrtzeit"], "7.0 -4.6 10.9": ["diglycol"], "-7.1 -3.1 -1.3": ["telerehabilitation"], "10.3 6.0 21.3": ["ovenware"], "2.2 5.3 3.3": ["radiosensitivity"], "6.6 12.0 23.0": ["albopictus"], "3.2 9.8 6.1": ["lendmanstephen"], "8.8 19.2 12.6": ["gulling"], "10.3 13.2 7.9": ["depolarized"], "-2.8 -1.2 1.6": ["graduand"], "-0.2 7.4 8.8": ["reparatory"], "6.2 -3.0 15.2": ["hippology"], "18.3 7.8 10.9": ["whassup"], "3.8 6.9 9.9": ["cclcclccl"], "5.0 14.4 13.2": ["southgate"], "-0.7 12.1 11.4": ["expandables"], "12.3 9.5 -1.7": ["immortalisation"], "12.4 10.8 11.2": ["microgrippers"], "22.5 17.3 25.5": ["slurpers"], "2.1 7.2 8.5": ["defrozen"], "7.5 7.7 2.0": ["guaran"], "26.0 10.1 3.3": ["arbitrager"], "9.3 10.8 4.4": ["lovefests"], "4.6 3.0 10.5": ["ukrainian"], "9.4 6.7 8.2": ["goodnights"], "2.0 20.9 3.2": ["devolutionist"], "1.9 5.5 15.1": ["jcm"], "17.3 18.1 24.2": ["mynas"], "9.4 23.5 15.4": ["raceless"], "7.0 2.6 14.6": ["rolle"], "6.2 16.4 0.5": ["ghettoise"], "2.0 6.8 12.0": ["stockbreeders"], "-5.6 18.9 -0.2": ["jurisprudents"], "2.4 3.3 29.0": ["chevon"], "9.7 11.6 15.9": ["hore"], "1.2 10.9 11.3": ["wapas"], "-4.7 4.6 -1.9": ["ciclosporin"], "19.8 17.0 20.2": ["rubbled"], "8.1 28.0 21.7": ["merchantman"], "18.2 5.6 12.8": ["polydimethylsiloxane"], "2.4 13.7 5.3": ["contrastive"], "8.2 6.7 8.6": ["andout"], "7.4 6.4 13.8": ["volcaniclastics"], "3.5 6.4 11.8": ["deta"], "3.3 4.5 -3.6": ["releaved"], "4.5 8.9 8.8": ["calomel"], "9.3 14.8 13.5": ["straitjacketing"], "-2.9 29.2 5.9": ["sacrfice"], "-1.4 7.9 0.9": ["polesitters"], "5.4 8.2 9.3": ["esos"], "-12.0 9.7 3.9": ["stb"], "13.0 22.4 8.3": ["medialand"], "4.5 2.7 12.7": ["prilosec"], "12.8 10.6 20.4": ["overpaint"], "4.1 4.2 7.7": ["ocularist"], "2.3 10.3 3.4": ["usar"], "13.9 6.8 21.8": ["basketweaving"], "2.4 -0.5 3.4": ["ethica"], "-3.1 10.3 10.3": ["saad"], "-1.0 4.4 1.1": ["cardiologic"], "3.6 11.2 0.4": ["overmedicate"], "-7.8 7.2 1.0": ["todetermine"], "2.6 4.3 8.7": ["dahilan"], "21.9 19.0 16.3": ["rottweiller"], "18.6 13.0 20.7": ["blowtorched"], "10.2 13.5 15.8": ["uncrating"], "10.4 6.1 -0.3": ["mismanagment"], "3.1 9.9 7.2": ["erotics"], "7.5 16.1 14.3": ["sideslip"], "2.9 2.4 8.3": ["lymphangiogenesis"], "3.2 14.5 6.2": ["incunabula"], "10.3 23.8 9.5": ["casemates"], "-0.9 3.7 15.3": ["basinal"], "-1.2 5.3 0.6": ["unapplied"], "5.9 1.8 20.8": ["nourishments"], "15.5 -5.2 -0.3": ["nieuw"], "0.7 11.6 9.4": ["kippas"], "10.7 21.9 12.1": ["archconservatives"], "30.0 4.8 20.2": ["balsawood"], "14.8 15.7 18.7": ["dwight"], "13.6 0.5 2.9": ["bruhaha"], "4.2 18.0 8.4": ["satyagrah"], "16.8 30.4 18.8": ["spinless"], "25.4 19.8 13.7": ["vastest"], "5.5 13.0 9.5": ["hume"], "4.0 17.2 -5.0": ["interworkings"], "0.6 9.4 10.6": ["unattainably"], "11.0 23.3 12.0": ["jeebies"], "10.1 14.4 11.5": ["assy"], "6.6 2.6 3.5": ["immerging"], "3.0 24.8 8.8": ["plebiscitary"], "19.3 5.6 2.9": ["carmarkers"], "13.7 6.3 19.6": ["loden"], "6.0 1.9 -2.3": ["pointsperson"], "4.4 8.5 1.8": ["vms"], "15.4 9.9 13.1": ["spunkiest"], "14.8 6.2 31.9": ["globby"], "15.8 2.1 11.4": ["polyethelene"], "18.3 4.8 21.0": ["hypercube"], "12.6 11.8 6.4": ["dodgey"], "-8.2 7.7 1.3": ["auditee"], "7.0 7.8 14.1": ["staffrooms"], "12.0 4.9 15.4": ["dyna"], "8.9 4.3 8.4": ["reposessions"], "3.4 8.1 11.0": ["theke"], "4.1 9.9 11.1": ["schoolgrounds"], "15.3 11.2 -0.2": ["worldbeater"], "10.6 -1.3 11.5": ["dolllars"], "4.2 23.5 -1.9": ["assualts"], "0.9 4.7 12.2": ["hildren"], "3.9 21.6 35.2": ["moana"], "15.2 -5.3 -6.7": ["buld"], "8.8 10.9 10.4": ["chattin"], "-0.7 5.5 9.8": ["conspicious"], "10.5 16.6 19.4": ["hadda"], "-2.7 2.5 12.5": ["trom"], "21.8 4.0 20.2": ["tinselly"], "-0.6 8.4 12.4": ["theprior"], "1.3 14.7 12.8": ["hether"], "9.0 -1.8 12.4": ["showmobile"], "10.5 9.1 15.6": ["taurus"], "2.7 12.6 8.2": ["offeseason"], "6.6 10.3 17.0": ["kineticism"], "-3.8 15.8 7.1": ["civi"], "7.8 -0.4 17.0": ["palaeoanthropologist"], "7.0 13.9 16.4": ["transpolar"], "7.5 4.0 17.6": ["triphala"], "1.5 10.5 2.1": ["karein"], "8.8 3.5 21.5": ["barkeepers"], "5.5 5.4 5.5": ["toeloop"], "-1.5 19.0 21.8": ["sakti"], "11.7 15.1 2.5": ["unnanounced"], "3.2 7.8 13.5": ["benson"], "1.0 10.1 3.8": ["seconday"], "-0.6 7.7 1.4": ["pesonal"], "0.5 17.9 13.3": ["hamesha"], "13.0 10.9 30.8": ["bahia"], "0.0 2.9 0.9": ["imple"], "11.8 2.2 23.5": ["saratoga"], "3.5 12.5 14.3": ["fensive"], "15.1 10.4 18.7": ["sulpher"], "2.3 3.0 11.4": ["avearge"], "4.5 17.0 1.6": ["changemaker"], "23.2 20.0 17.7": ["uncurling"], "21.4 19.2 20.5": ["goatish"], "-1.8 11.8 10.8": ["gamitin"], "3.0 13.2 9.9": ["whaaa"], "14.0 12.2 16.6": ["unlacing"], "4.4 18.6 1.2": ["palling"], "19.0 5.9 14.2": ["springerle"], "5.0 19.8 9.9": ["salaams"], "9.6 2.5 12.9": ["autophagosomes"], "-1.8 -3.0 9.9": ["versity"], "2.7 -4.9 9.0": ["preanalytical"], "15.0 5.3 36.4": ["cornichon"], "6.1 13.2 5.7": ["centurian"], "7.8 1.2 11.7": ["permiso"], "5.8 -1.1 -1.6": ["klm"], "14.6 2.9 4.0": ["photobucket"], "5.1 2.5 10.2": ["bsu"], "9.2 17.6 4.5": ["interrelating"], "13.0 10.4 11.4": ["firme"], "19.7 14.6 28.6": ["hackberries"], "8.3 -0.8 -1.3": ["inder"], "17.4 13.0 14.7": ["megapopular"], "24.0 12.6 11.8": ["soccerball"], "-6.7 11.8 10.2": ["passsenger"], "14.6 3.9 26.8": ["elote"], "4.7 -0.8 8.0": ["ators"], "19.4 7.2 24.3": ["waterskis"], "6.1 18.8 6.7": ["emergents"], "1.7 8.3 4.0": ["webservice"], "3.5 8.4 7.2": ["resubscribe"], "8.8 3.3 2.9": ["zien"], "10.2 16.4 18.6": ["powerslammed"], "2.4 -2.1 -2.0": ["senoir"], "-2.0 26.3 8.6": ["unwisdom"], "1.3 0.4 8.1": ["renamings"], "8.5 15.4 10.2": ["garimpo"], "2.4 12.6 13.2": ["butchness"], "14.8 6.0 14.9": ["monofilaments"], "-2.2 -5.2 1.2": ["opment"], "0.2 2.0 0.3": ["mhd"], "1.9 1.1 -0.7": ["opthamologists"], "10.8 13.2 7.9": ["vidoe"], "8.8 14.5 9.0": ["geniunely"], "2.2 25.8 -1.2": ["nationalistically"], "-1.8 4.6 4.3": ["replanned"], "6.4 24.4 7.4": ["physicalled"], "27.5 1.6 -1.3": ["subsiduary"], "7.0 2.9 3.1": ["shoeshines"], "7.2 14.6 6.8": ["cordycepin"], "-3.6 -15.6 -1.4": ["nonsubscription"], "13.0 11.4 -0.3": ["roled"], "-1.1 16.6 -1.4": ["problematics"], "12.3 25.3 1.5": ["antiballistic"], "4.9 16.9 6.5": ["troposcatter"], "15.1 0.2 2.2": ["deisgned"], "7.9 -0.3 3.1": ["polygeneration"], "2.4 11.0 13.8": ["freehub"], "-8.8 -3.3 5.4": ["prese"], "4.5 19.9 12.2": ["ofyour"], "5.6 8.2 4.9": ["eux"], "-3.1 4.4 -0.4": ["peacefmonline"], "7.9 6.5 1.2": ["stati"], "5.8 -2.4 10.6": ["toschool"], "2.3 16.2 8.0": ["nonconsenting"], "10.3 10.2 8.6": ["arsey"], "6.2 8.0 11.2": ["miling"], "11.2 -2.5 3.3": ["annuncia"], "8.5 15.3 11.9": ["chimere"], "12.3 25.9 19.0": ["injun"], "8.9 -2.8 2.6": ["remarkets"], "2.3 -3.1 12.9": ["netfest"], "14.2 5.5 7.8": ["bonusgate"], "-8.4 12.7 4.2": ["upstater"], "9.9 10.5 5.7": ["unaffecting"], "-0.4 8.0 17.6": ["isyu"], "-3.4 24.1 -2.0": ["commandership"], "8.1 22.9 12.3": ["keepeth"], "12.8 3.7 3.0": ["mouvement"], "2.5 9.9 16.8": ["kut"], "0.3 7.4 -2.4": ["reitereated"], "2.9 18.4 -2.9": ["theneed"], "8.5 10.0 11.9": ["impalements"], "9.8 11.2 7.7": ["sparmate"], "18.2 8.3 13.6": ["steamroom"], "0.5 13.0 5.8": ["anycast"], "2.6 6.1 6.0": ["coac"], "4.0 20.2 9.1": ["bullys"], "8.6 25.0 4.2": ["nudnik"], "-3.4 13.1 8.8": ["isse"], "1.5 4.2 14.9": ["osteopetrosis"], "5.4 7.1 3.1": ["mininotebook"], "9.9 12.0 4.9": ["anotehr"], "11.7 20.6 23.0": ["mudball"], "-3.0 2.3 5.2": ["triiodothyronine"], "8.5 16.2 10.5": ["oranje"], "0.8 22.1 10.0": ["carnappers"], "9.2 14.7 9.7": ["polizia"], "10.9 3.1 36.0": ["piperade"], "2.8 13.9 10.4": ["hominis"], "-2.3 11.2 11.0": ["viabilities"], "5.9 10.8 22.2": ["quacky"], "12.5 8.1 14.6": ["surfeited"], "0.1 2.9 11.6": ["psilocin"], "-2.6 1.4 21.0": ["oloroso"], "6.0 2.8 14.1": ["frontera"], "0.5 5.6 -1.0": ["cect"], "2.3 4.0 5.2": ["leaseable"], "0.5 -2.3 -0.4": ["regenerable"], "-2.7 20.2 4.1": ["interefere"], "14.1 3.2 24.7": ["potica"], "-0.9 7.2 14.5": ["ninong"], "-8.0 12.8 -0.7": ["addingthat"], "10.4 14.0 32.4": ["bettas"], "2.5 0.5 0.4": ["monthend"], "-4.6 4.4 2.6": ["guarentees"], "15.8 7.3 33.8": ["hootchies"], "-0.5 6.9 9.2": ["nonstrike"], "14.1 -2.2 7.6": ["earnin"], "1.8 13.8 -4.5": ["hoorai"], "12.1 29.5 4.7": ["metastasising"], "2.7 16.8 5.0": ["undogmatic"], "8.3 0.8 12.5": ["clara"], "14.4 5.3 6.4": ["knacked"], "3.3 14.2 -0.5": ["abstentionist"], "7.0 10.8 9.9": ["visiblity"], "14.0 12.8 7.2": ["transepts"], "24.3 8.4 5.1": ["preinstalling"], "10.9 23.7 8.8": ["joltingly"], "25.3 19.9 27.6": ["tanuki"], "18.5 2.2 8.0": ["bango"], "6.8 0.8 8.6": ["fthe"], "8.0 6.8 1.8": ["upscaler"], "15.0 9.9 15.1": ["abseiler"], "-1.8 11.6 5.7": ["protectedpdf"], "12.1 3.5 6.5": ["nukkad"], "10.1 4.4 18.6": ["hakama"], "10.7 9.8 24.5": ["schipperke"], "-1.5 -5.8 -0.9": ["contactus"], "10.7 27.8 8.1": ["blindest"], "4.4 5.5 7.7": ["kippahs"], "-2.5 4.9 8.9": ["ileitis"], "6.1 -4.2 8.5": ["lowerthan"], "8.3 -7.2 3.3": ["pfu"], "13.7 1.0 12.6": ["upholsters"], "5.3 11.8 13.3": ["premolar"], "5.5 3.3 8.2": ["sauve"], "9.2 13.0 37.8": ["drumettes"], "10.7 8.7 5.9": ["fffh"], "7.1 16.2 3.2": ["demonstations"], "18.6 9.3 16.8": ["granulating"], "6.6 -3.7 -1.9": ["gvernment"], "10.1 18.6 5.9": ["germaphobic"], "15.5 19.6 26.2": ["spongey"], "-0.4 1.4 4.4": ["mito"], "3.7 6.3 12.4": ["gasless"], "13.8 18.1 20.3": ["cryptozoological"], "16.9 9.9 13.9": ["bobbysoxers"], "6.7 18.7 15.2": ["muchacho"], "0.2 4.9 -1.0": ["synthesist"], "1.5 0.7 1.3": ["immunocytochemistry"], "11.0 1.8 18.3": ["kame"], "6.0 8.5 2.6": ["unviability"], "10.6 16.7 5.8": ["esepcially"], "-9.0 1.2 3.5": ["postinjury"], "-0.6 14.8 5.8": ["vipassana"], "25.1 9.3 27.2": ["rosellas"], "2.4 16.9 3.1": ["antidotal"], "7.6 -3.5 5.7": ["phen"], "8.7 0.9 10.9": ["dows"], "-1.9 8.1 0.5": ["allso"], "19.6 20.9 19.8": ["palings"], "5.2 9.0 10.1": ["moanin"], "0.4 5.2 1.9": ["crossflow"], "-1.8 1.1 3.1": ["wote"], "12.0 5.8 10.6": ["intruments"], "12.6 13.0 33.7": ["antipasta"], "-6.8 -0.1 2.2": ["talled"], "9.8 10.9 18.3": ["hemolymph"], "3.0 5.7 10.6": ["kvm"], "7.4 17.0 2.2": ["unadvisedly"], "9.9 9.4 6.5": ["reprojection"], "7.9 10.7 13.7": ["yaga"], "14.3 8.6 2.4": ["touchphone"], "-0.5 10.5 3.7": ["defination"], "17.9 6.0 27.6": ["polony"], "7.1 -4.2 15.3": ["glyco"], "13.8 29.9 15.2": ["deathlike"], "0.9 26.8 10.8": ["epistemologically"], "6.2 5.1 7.7": ["greenshoots"], "-0.3 9.0 10.8": ["neurocysticercosis"], "-5.2 16.8 -0.2": ["mahallas"], "7.3 5.4 11.6": ["endermologie"], "9.4 10.9 9.8": ["beidentified"], "9.4 14.0 14.8": ["spoonfeed"], "16.2 6.7 27.0": ["chim"], "6.6 8.6 16.2": ["hardballers"], "9.8 7.6 6.7": ["reskinning"], "2.3 -0.8 0.8": ["compen"], "2.8 5.5 17.0": ["pdc"], "19.2 9.6 11.9": ["whisp"], "17.0 3.8 7.1": ["asteroseismology"], "13.8 16.0 14.2": ["gabba"], "5.0 -3.7 24.1": ["maincrop"], "12.8 16.9 17.9": ["subsistance"], "-1.4 13.6 0.6": ["indicitive"], "5.0 15.7 3.9": ["righters"], "1.8 5.4 18.1": ["wari"], "11.9 9.7 11.5": ["semaine"], "5.7 5.9 25.4": ["necropsied"], "2.1 16.9 12.3": ["himand"], "16.7 1.3 7.2": ["delievery"], "4.6 5.8 9.8": ["principe"], "2.8 0.0 11.4": ["pratique"], "4.6 3.5 18.0": ["baseyard"], "8.5 2.7 14.4": ["anita"], "8.0 11.5 16.9": ["allin"], "9.5 13.7 9.9": ["stockholm"], "1.5 8.5 12.5": ["fivegame"], "18.7 8.0 12.9": ["hocky"], "10.1 5.3 16.0": ["selenite"], "7.4 5.7 4.9": ["ofone"], "2.6 8.6 8.9": ["satis"], "0.3 1.6 5.2": ["cabined"], "0.9 4.1 6.4": ["beatboxed"], "0.7 6.1 2.6": ["deduplicates"], "-6.4 8.3 5.5": ["aneuploidies"], "12.7 0.8 12.6": ["dicovered"], "9.0 45.8 16.5": ["spearmen"], "14.0 19.9 27.7": ["icefalls"], "-0.3 -2.4 2.3": ["pape"], "16.7 15.0 -0.6": ["mutedly"], "7.6 8.5 11.4": ["flavin"], "12.2 14.8 12.3": ["circumambulating"], "1.9 18.4 9.7": ["billyclubs"], "7.8 9.1 12.5": ["nanobelts"], "1.2 -1.5 -2.4": ["compaint"], "0.9 4.0 17.8": ["synbiotic"], "2.7 -4.2 -3.1": ["neurosurgeries"], "14.3 0.5 15.9": ["innersprings"], "7.9 15.0 8.8": ["thepossibility"], "24.2 15.3 37.0": ["taimen"], "7.9 18.3 15.5": ["germaphobes"], "8.4 19.8 7.8": ["constitues"], "14.2 0.9 8.4": ["nematic"], "1.9 5.8 4.7": ["thecost"], "13.3 7.2 31.2": ["pochard"], "5.6 13.7 7.1": ["northsiders"], "4.2 9.6 42.8": ["spearfishers"], "3.1 11.6 11.1": ["jockish"], "0.5 17.3 13.2": ["baaaaaack"], "5.6 8.0 20.4": ["serrata"], "8.8 21.2 37.0": ["callibaetis"], "0.8 6.7 3.5": ["recompetition"], "-0.5 -0.2 13.9": ["pyrene"], "16.4 5.3 18.2": ["bargeboard"], "13.7 3.1 14.9": ["ethan"], "-0.6 15.4 10.8": ["shivah"], "-1.3 14.5 -2.6": ["shoora"], "-6.5 0.3 -2.4": ["chargesheeting"], "2.2 15.4 13.9": ["sombreness"], "3.6 8.6 16.9": ["holl"], "16.3 10.6 9.1": ["thicko"], "12.0 14.4 4.5": ["beatmaster"], "11.6 15.8 10.7": ["campmate"], "1.9 -8.1 11.8": ["kets"], "5.3 -1.0 1.0": ["additionto"], "15.1 10.3 1.3": ["misteps"], "4.6 10.3 2.8": ["copyable"], "10.8 25.6 15.0": ["outbreed"], "6.4 -7.9 -2.8": ["internat"], "-2.1 26.3 5.2": ["refinding"], "5.4 5.2 17.4": ["saman"], "7.9 15.2 8.2": ["unlearnt"], "18.1 12.3 28.5": ["kalanchoes"], "-5.7 3.3 -2.8": ["investigtion"], "-1.2 12.2 2.9": ["arteriogram"], "5.7 17.6 9.9": ["noticible"], "-2.5 4.3 -0.0": ["orgnisation"], "13.5 6.0 17.8": ["mauvais"], "-1.5 24.5 10.9": ["habibi"], "-2.7 -7.9 -6.4": ["newletter"], "1.9 17.6 8.8": ["priniciple"], "3.7 2.8 6.3": ["syngeneic"], "3.2 7.2 10.4": ["subregisters"], "17.9 7.4 26.5": ["clivias"], "18.8 8.4 8.1": ["coporations"], "14.8 3.7 26.6": ["bedskirt"], "14.1 20.1 13.3": ["meeee"], "11.3 20.5 8.6": ["stalinist"], "0.5 22.7 17.9": ["cuckoldry"], "21.2 12.5 2.8": ["massmarket"], "16.6 13.2 32.0": ["pescetarian"], "4.1 5.3 18.3": ["courir"], "12.1 0.1 10.3": ["mangalsutras"], "13.0 10.4 22.5": ["lanugo"], "8.3 14.6 14.3": ["angularly"], "2.2 2.4 -4.6": ["gartner"], "6.8 7.2 14.8": ["hominoids"], "10.7 2.1 13.2": ["vinery"], "-2.1 -2.9 -3.7": ["demitted"], "1.8 11.2 0.0": ["newbook"], "14.3 8.7 13.7": ["flannelled"], "6.1 21.9 10.2": ["muddleheaded"], "2.1 12.9 12.7": ["reintensify"], "8.4 10.7 16.1": ["resue"], "-0.4 9.0 8.1": ["demodulates"], "3.7 -0.2 -3.6": ["lndia"], "4.8 12.8 7.5": ["paramyxoviruses"], "-6.7 -1.7 1.8": ["certi"], "3.4 0.8 10.7": ["underpriveleged"], "10.5 11.7 6.2": ["baliffs"], "8.9 11.7 13.2": ["sectored"], "5.4 8.4 18.0": ["hopple"], "10.2 3.9 7.3": ["multiseat"], "14.7 -0.2 11.0": ["staterun"], "6.0 10.5 15.5": ["neighboured"], "9.1 -1.6 12.4": ["ondes"], "13.4 17.9 20.0": ["verrucas"], "4.1 16.1 10.1": ["freqs"], "8.5 8.3 -2.2": ["runnig"], "7.3 -2.0 14.8": ["specail"], "-2.2 0.4 4.5": ["osteoconductive"], "11.4 3.1 13.8": ["hydrokinetics"], "3.6 -1.4 1.9": ["interuniversity"], "3.4 9.5 20.7": ["bryophytes"], "4.1 9.2 11.9": ["mmwave"], "2.3 0.8 13.5": ["yearto"], "-2.8 22.1 9.4": ["playcalls"], "11.2 27.8 13.5": ["spaniards"], "-4.3 9.4 3.8": ["cde"], "7.4 13.0 16.3": ["pushoff"], "3.6 1.0 13.5": ["sers"], "5.6 -1.0 13.6": ["propre"], "0.6 22.9 10.6": ["repugnancy"], "4.7 -6.4 -6.8": ["outling"], "7.3 16.6 4.5": ["lookat"], "3.4 17.8 12.9": ["anecdotage"], "7.8 17.2 26.9": ["ectotherms"], "2.8 0.5 -7.6": ["proformas"], "12.4 18.7 7.2": ["bipartisanism"], "1.7 -7.1 -8.4": ["challeneged"], "14.9 -0.1 9.1": ["bohos"], "3.7 25.9 6.5": ["assimilationists"], "12.2 10.5 10.9": ["desalinisation"], "3.0 2.6 6.1": ["kerberos"], "13.5 12.8 9.6": ["photosensors"], "16.0 1.6 -5.5": ["speced"], "-3.2 14.2 -2.5": ["executer"], "19.3 17.7 16.2": ["fasces"], "2.3 24.0 10.4": ["forgivness"], "14.0 16.0 6.3": ["pedways"], "8.3 15.9 19.8": ["firstfruits"], "13.9 13.8 1.1": ["brandjacking"], "8.6 7.3 8.7": ["hydric"], "11.9 -0.4 12.7": ["harpin"], "-0.0 8.4 11.9": ["ihnen"], "1.9 14.8 5.5": ["deterioriation"], "15.0 -0.9 18.2": ["sippable"], "1.9 20.8 13.2": ["hannity"], "0.2 3.5 9.0": ["taarab"], "7.7 13.3 15.6": ["ihe"], "10.6 14.0 11.0": ["dubbers"], "-4.3 3.8 8.3": ["spective"], "7.6 16.8 2.6": ["guaged"], "5.7 30.7 -7.0": ["shootdowns"], "6.2 14.2 14.9": ["dukh"], "13.4 5.1 30.1": ["appies"], "13.0 8.4 26.5": ["umu"], "6.4 11.6 2.9": ["fourtime"], "1.1 7.3 11.0": ["rpc"], "14.8 -10.9 4.9": ["nch"], "-7.5 14.1 5.2": ["lovah"], "8.6 8.3 15.7": ["tora"], "13.6 1.7 12.1": ["biorepositories"], "5.4 1.4 6.0": ["retouchers"], "7.9 12.2 15.9": ["maaan"], "3.4 6.8 4.6": ["stellen"], "-4.0 3.6 2.2": ["rsc"], "1.9 -1.8 13.3": ["summerfest"], "-0.0 8.9 9.5": ["subsititute"], "25.0 11.7 14.3": ["tealight"], "0.2 16.9 -2.0": ["vanguardist"], "5.1 13.4 11.4": ["fortunates"], "13.7 21.3 14.1": ["nagin"], "2.6 12.3 -1.0": ["behav"], "7.4 13.9 12.4": ["dubplates"], "20.6 5.6 9.5": ["aline"], "13.5 4.1 2.8": ["elevenfold"], "3.7 19.3 11.0": ["mulishly"], "-3.4 10.7 13.0": ["electroacupuncture"], "22.6 14.1 18.7": ["blastin"], "12.3 1.5 3.2": ["fera"], "2.7 4.1 4.9": ["nonprogressive"], "22.4 3.8 14.3": ["overpackaged"], "12.2 8.2 0.9": ["hymnbooks"], "15.9 1.0 44.1": ["almondine"], "-5.1 16.0 13.5": ["gald"], "12.1 11.3 32.7": ["sapodilla"], "-2.3 8.2 17.4": ["tarian"], "19.2 11.5 24.3": ["tuscan"], "5.2 29.1 7.5": ["pauperizing"], "8.4 10.4 7.6": ["polyglots"], "8.6 6.5 -3.7": ["cinecast"], "-3.0 4.7 9.5": ["coachings"], "24.4 14.7 0.2": ["computerlike"], "11.4 0.9 5.5": ["genco"], "1.2 10.5 15.6": ["darcy"], "17.6 1.6 4.0": ["softwear"], "5.1 15.8 4.6": ["nonmilitarized"], "4.5 11.2 28.7": ["khai"], "12.0 -6.8 9.6": ["raquetball"], "4.0 -4.7 11.3": ["corte"], "-4.6 9.2 -0.3": ["apppointment"], "2.5 11.5 5.0": ["governo"], "16.4 17.2 18.0": ["scrying"], "8.2 15.9 8.3": ["rabblerouser"], "-0.9 6.6 7.0": ["summonsing"], "1.5 2.6 8.2": ["fwy"], "4.0 18.1 12.8": ["popery"], "6.9 18.3 9.0": ["kiran"], "6.3 7.8 11.1": ["oming"], "-7.6 7.4 1.5": ["prostacyclins"], "7.8 1.8 53.6": ["opakapaka"], "0.4 13.1 10.0": ["diahorrea"], "12.3 5.3 12.7": ["resilin"], "0.9 27.3 7.0": ["uneducable"], "2.6 12.1 8.6": ["procurable"], "24.7 20.6 22.0": ["pupating"], "-0.7 19.4 10.6": ["faulter"], "-4.2 7.0 2.6": ["substantiations"], "0.6 16.8 9.5": ["reak"], "5.5 1.5 11.9": ["nonaddictive"], "4.0 19.1 13.1": ["hilariousness"], "6.7 11.9 4.4": ["izquierda"], "2.9 -4.3 5.9": ["bahr"], "14.6 2.3 13.9": ["stripclub"], "11.0 13.9 16.3": ["judas"], "15.8 2.8 21.7": ["buk"], "5.3 4.1 -2.7": ["perferred"], "6.3 29.7 10.2": ["interiorly"], "1.9 14.8 6.7": ["occurrs"], "0.7 1.0 7.9": ["bitonal"], "2.6 5.4 21.4": ["vermouths"], "14.6 6.4 28.3": ["slabbing"], "3.2 19.0 0.9": ["depictive"], "8.1 7.4 6.0": ["rachets"], "5.8 7.2 17.0": ["maong"], "-2.3 15.2 4.1": ["uninfluential"], "11.4 26.3 5.6": ["succored"], "12.7 -0.4 9.5": ["regualtions"], "13.2 15.5 9.6": ["twiddly"], "14.1 5.2 -0.9": ["hairyfeet"], "11.0 2.8 5.6": ["bfi"], "0.2 9.1 19.4": ["quila"], "-3.3 6.1 1.6": ["knowledgeability"], "9.6 8.4 14.7": ["gassiness"], "12.4 14.8 20.8": ["hilling"], "-2.5 19.7 13.9": ["verticillium"], "-5.0 -0.8 13.5": ["signor"], "-4.6 -4.9 -2.1": ["gradates"], "2.6 10.9 -2.5": ["jeapordize"], "16.3 6.3 13.0": ["uncustomed"], "-2.8 5.9 1.7": ["flexeril"], "-11.3 -3.2 5.8": ["kowski"], "9.7 20.7 20.4": ["okami"], "12.7 1.3 1.6": ["ndian"], "7.4 4.6 30.0": ["waribashi"], "19.5 11.0 10.7": ["barkin"], "24.9 12.4 20.9": ["truckle"], "14.8 1.4 12.1": ["makets"], "3.0 20.3 13.6": ["happyness"], "-3.0 8.0 10.8": ["sepa"], "1.0 -5.3 8.0": ["riday"], "16.6 7.8 16.3": ["warmbloods"], "16.0 9.0 17.7": ["preakness"], "4.2 7.8 12.1": ["dehn"], "5.7 14.1 13.1": ["inferiorly"], "7.3 2.8 19.3": ["boswellia"], "3.2 16.7 8.7": ["havildars"], "-6.3 6.8 8.1": ["loopbacks"], "2.2 17.1 5.2": ["dhyana"], "6.9 22.6 11.7": ["antinomian"], "10.6 4.0 0.2": ["sauvegarde"], "14.1 10.8 14.4": ["gonging"], "-4.0 17.2 10.4": ["delimitations"], "-4.1 9.0 2.7": ["oblimersen"], "7.1 -3.5 4.0": ["iting"], "3.6 -1.0 15.6": ["lindo"], "12.0 12.6 0.8": ["isgoing"], "4.2 7.8 2.6": ["accessor"], "3.1 5.1 1.7": ["pendrive"], "13.7 10.5 12.7": ["primative"], "27.3 8.8 24.7": ["gobstoppers"], "9.0 6.3 0.2": ["geocoder"], "14.2 17.5 8.9": ["increasinly"], "6.0 14.1 9.7": ["batle"], "8.7 16.6 8.0": ["kludges"], "11.6 8.1 9.2": ["toput"], "18.5 13.7 8.9": ["jumplists"], "-2.7 3.5 6.1": ["caratage"], "8.5 2.9 16.6": ["keeshond"], "-0.3 10.4 11.7": ["secondbaseman"], "-5.7 17.2 11.4": ["gradualness"], "3.9 13.8 14.3": ["eventaully"], "6.4 8.3 5.9": ["looing"], "3.6 18.5 10.1": ["unsettledness"], "12.3 8.6 17.5": ["underprocessed"], "-1.1 14.7 7.8": ["ostensive"], "8.7 0.2 1.0": ["reregulating"], "-0.4 -2.4 2.9": ["rabeprazole"], "0.4 4.6 4.9": ["chlorobenzene"], "20.5 17.6 22.4": ["sabertooth"], "16.5 8.1 44.6": ["pumpkinseeds"], "-1.0 10.5 13.8": ["intercostals"], "13.8 2.1 9.1": ["shopfitters"], "9.6 -5.5 3.6": ["alegra"], "31.0 10.7 26.0": ["cowpie"], "-7.7 9.3 2.8": ["pubwatch"], "15.5 11.6 0.1": ["interational"], "17.2 14.2 15.7": ["glazers"], "12.0 19.9 9.7": ["trods"], "15.3 7.2 31.1": ["petai"], "10.1 7.8 13.6": ["dielectrophoresis"], "9.3 13.2 13.5": ["noxiously"], "7.5 5.9 7.4": ["freedocast"], "-0.5 31.4 6.6": ["comand"], "23.8 10.7 21.5": ["cloudscape"], "2.2 18.9 15.4": ["tensional"], "4.1 -1.5 9.8": ["babymoons"], "9.5 7.8 8.1": ["multipartner"], "10.1 1.0 14.8": ["splashpad"], "6.3 2.8 0.9": ["neuroregeneration"], "4.0 6.3 15.7": ["dunkel"], "8.5 23.6 -0.7": ["accussing"], "4.4 11.5 10.1": ["venir"], "-0.2 7.2 2.6": ["lating"], "0.4 20.5 16.8": ["handpassing"], "7.7 4.4 10.4": ["pensione"], "5.2 7.3 19.6": ["bethel"], "3.6 6.8 9.9": ["specificly"], "3.5 10.2 23.6": ["locs"], "19.1 16.0 25.9": ["ringtail"], "12.8 10.5 6.6": ["rase"], "2.9 4.0 3.5": ["eventline"], "3.1 -8.4 -7.5": ["workwith"], "11.9 20.9 8.0": ["enduing"], "6.8 23.5 2.0": ["islanded"], "11.8 8.3 8.0": ["compactable"], "4.5 18.2 9.1": ["builded"], "14.1 -4.0 0.6": ["onlin"], "5.3 27.5 5.8": ["themilitary"], "3.8 12.5 6.1": ["groundspeed"], "2.6 11.1 6.9": ["overprovisioning"], "6.6 13.1 16.7": ["korowai"], "14.0 14.7 16.7": ["micronation"], "2.1 5.2 5.5": ["cordierite"], "15.3 3.7 12.7": ["unknotting"], "7.7 9.9 4.5": ["itsmilife"], "11.1 0.7 36.5": ["sherried"], "0.4 4.3 3.1": ["solictor"], "6.5 4.4 18.2": ["ecotoxicity"], "16.1 18.7 25.9": ["derailer"], "11.4 -2.2 10.5": ["yez"], "5.2 13.1 6.7": ["initialy"], "12.5 9.8 9.9": ["clubbish"], "10.5 2.4 3.3": ["gassification"], "-4.3 -3.7 -0.5": ["conluded"], "11.1 9.6 30.6": ["shadbush"], "2.9 9.7 22.5": ["fastcraft"], "-6.4 0.8 -0.3": ["ndez"], "6.5 25.7 3.1": ["blantantly"], "2.6 7.6 7.5": ["dete"], "8.6 12.6 1.3": ["cosmonautics", "citites"], "0.6 18.3 8.6": ["butwe"], "2.9 -9.9 -0.7": ["dirctor"], "7.6 10.8 21.0": ["kunafa"], "11.5 8.2 14.0": ["desexualized"], "18.9 16.8 37.2": ["mahseer"], "14.5 12.3 8.2": ["feminise"], "14.0 17.1 4.2": ["thewhole"], "11.9 11.0 10.8": ["braggy"], "-3.7 9.8 18.5": ["pcij"], "11.2 14.9 24.5": ["chok"], "-0.2 4.9 14.4": ["ahjar"], "3.5 0.6 5.8": ["vihch"], "4.3 14.9 14.3": ["behen"], "8.3 -1.5 4.0": ["euroyen"], "12.1 22.3 11.9": ["beig"], "5.8 15.3 3.3": ["aeromodelling"], "18.6 9.8 22.1": ["corbel"], "11.1 5.9 13.1": ["youngbloods"], "-3.7 18.8 11.0": ["multiplicitous"], "0.5 11.7 7.2": ["picturise"], "6.1 7.0 17.4": ["poteen"], "12.1 13.2 9.0": ["lullabye"], "1.5 7.9 12.5": ["kalan"], "5.3 4.8 5.8": ["pim"], "8.2 16.0 9.2": ["multipled"], "7.7 4.5 3.9": ["arma"], "7.7 28.8 23.3": ["minelayer"], "0.6 1.8 9.1": ["kollha"], "8.4 -0.9 34.6": ["calabrese"], "18.2 24.7 9.8": ["ahole"], "13.1 24.2 7.3": ["faggotry"], "8.7 7.6 20.5": ["thighbones"], "7.9 15.7 12.8": ["candi"], "-2.4 -0.3 13.1": ["igo"], "20.4 12.6 8.9": ["ngoma"], "4.4 14.0 17.1": ["sumpin"], "15.0 23.1 35.3": ["mantids"], "7.3 -1.6 13.4": ["iaith"], "6.1 11.5 14.6": ["wairua"], "14.6 22.8 12.8": ["tigerishly"], "15.3 23.6 7.8": ["primally"], "8.6 9.0 3.9": ["circumferentially"], "9.2 6.7 12.5": ["fileds"], "10.9 19.0 16.2": ["allll"], "-2.3 -2.9 9.2": ["meeti"], "10.9 3.6 18.9": ["humilis"], "12.1 14.3 8.4": ["transmutations"], "14.6 13.5 19.2": ["naruto"], "15.7 32.9 16.4": ["superflu"], "9.4 15.9 9.2": ["particualr"], "-1.2 -2.6 -2.9": ["availablefor"], "3.1 -1.7 4.5": ["anniversaried"], "11.1 7.8 2.5": ["leveragable"], "9.7 2.1 11.9": ["soundchecking"], "5.6 3.8 11.6": ["quartermile"], "0.8 0.2 11.3": ["legiters"], "11.3 7.3 7.0": ["onze"], "3.9 4.5 4.9": ["immunoglobin"], "15.4 6.0 15.4": ["bonze"], "26.4 -10.0 4.9": ["pharmacuetical"], "5.4 33.8 2.6": ["expansionistic"], "17.7 6.7 9.8": ["reminicent"], "11.9 33.3 7.7": ["eschaton"], "2.6 8.9 11.1": ["dous"], "2.9 -1.3 11.6": ["showhouses"], "12.7 18.7 2.8": ["funtionality"], "-6.3 13.8 11.9": ["immunotoxins"], "8.4 1.7 5.6": ["ultralounge"], "17.1 13.6 16.8": ["mislabled"], "7.3 16.5 13.4": ["vato"], "10.5 15.6 5.5": ["eroticize"], "-1.3 10.5 0.7": ["contractholders"], "-0.5 12.4 8.3": ["illum"], "2.9 28.5 7.3": ["situtations"], "6.7 14.2 14.8": ["reclog"], "1.4 19.1 6.3": ["apreciate"], "-2.1 5.4 5.6": ["intere"], "17.3 11.3 31.3": ["unfertilised"], "4.5 9.2 7.4": ["insipidness"], "8.0 23.4 20.6": ["supertaster"], "15.4 11.2 18.1": ["ricefield"], "5.9 10.3 2.3": ["homeand"], "4.0 6.1 15.1": ["overemphatic"], "2.4 12.1 8.0": ["antievolution"], "9.7 0.8 9.0": ["cliams"], "16.9 5.2 13.0": ["duomo"], "-0.7 3.6 13.2": ["liquoring"], "-0.2 9.9 9.5": ["chyrons"], "3.4 0.0 9.4": ["newsrack"], "6.1 7.5 9.8": ["mazdoor"], "21.4 11.8 28.4": ["ganders"], "-0.1 16.3 7.7": ["knowlegable"], "10.3 3.4 10.2": ["clickair"], "3.4 9.5 12.5": ["eluvial"], "2.5 0.4 16.1": ["cyngor"], "4.8 9.6 8.6": ["vaso"], "4.3 17.0 5.9": ["overcooling"], "8.7 18.2 9.8": ["badassness"], "13.2 0.1 23.5": ["seltzers"], "-13.7 9.1 10.1": ["familicides"], "-0.2 31.1 2.8": ["personnnel"], "11.5 15.4 6.8": ["ganglands"], "-0.1 26.8 -1.3": ["nationbuilding"], "4.9 2.4 15.3": ["obra"], "10.4 16.3 16.6": ["cums"], "-3.8 8.6 13.9": ["annuitise"], "7.3 7.4 9.7": ["tourn"], "-0.8 1.4 2.3": ["reali"], "-4.3 8.9 4.2": ["tenureship"], "12.9 6.9 4.0": ["streakier"], "1.1 10.3 10.1": ["cacheable"], "6.5 0.2 -2.9": ["spirometers"], "8.9 0.5 5.3": ["reliquify"], "2.9 14.6 11.1": ["intrasquads"], "14.7 3.9 12.4": ["electrocoat"], "16.2 20.6 6.5": ["philippic"], "19.0 10.6 4.8": ["gamified"], "-1.6 6.7 8.2": ["educaton"], "13.1 25.0 16.6": ["claycourters"], "16.0 -1.3 0.4": ["annnouncement"], "10.8 13.4 16.7": ["phredicles"], "1.7 14.3 8.3": ["magnetise"], "6.6 8.9 15.1": ["demineralized"], "8.0 9.1 6.3": ["worred"], "6.0 11.6 7.6": ["micromanipulator"], "6.7 18.4 3.6": ["seprate"], "4.6 3.8 6.1": ["zarzuelas"], "5.2 4.2 7.5": ["malposition"], "-4.8 -1.8 3.5": ["quorate"], "10.0 17.4 1.6": ["selfserving"], "-8.5 6.7 -1.3": ["interesed"], "-0.5 6.1 8.1": ["discusssion"], "6.4 6.0 7.3": ["respecitvely"], "0.5 -0.5 0.8": ["radiotherapists"], "14.7 14.7 23.3": ["gasol"], "-2.5 13.2 1.1": ["xxxii"], "6.8 1.6 4.5": ["commisson"], "0.1 11.5 5.5": ["ulitmately"], "12.6 11.8 -3.1": ["codeveloping"], "16.7 6.5 4.6": ["chainstores"], "0.2 10.5 16.1": ["polyandrous"], "-8.1 -4.2 -7.8": ["transcripted"], "13.8 10.9 20.7": ["themeless"], "10.1 -5.4 5.1": ["ofrece"], "14.0 10.0 20.1": ["iggy"], "6.6 1.4 14.8": ["rialto"], "5.5 12.7 12.1": ["tahir"], "4.0 9.0 8.4": ["largley"], "5.6 -3.3 7.9": ["synthases"], "-4.8 11.8 12.2": ["wasy"], "2.1 12.3 3.6": ["approching"], "0.3 12.1 2.7": ["jathedars"], "8.0 9.4 18.2": ["floo"], "8.0 4.7 7.8": ["sanitations"], "-1.4 11.6 15.2": ["demandingly"], "9.5 -0.6 18.4": ["gmc"], "7.7 -7.9 8.6": ["fesitval"], "7.2 13.4 6.9": ["outprice"], "20.1 14.7 37.1": ["insectivore"], "1.7 12.5 9.7": ["nayika"], "6.8 9.1 14.6": ["archaisms"], "-0.8 1.7 1.2": ["guez"], "3.0 7.9 10.3": ["subah"], "7.5 15.1 6.1": ["eforts"], "14.4 14.5 14.7": ["odalisques"], "-0.2 -2.0 10.9": ["zygotic"], "14.8 8.7 37.2": ["meated"], "5.4 9.8 3.7": ["eclectics"], "5.1 13.8 10.0": ["wireframed"], "3.5 7.8 5.7": ["incom"], "2.9 7.9 4.5": ["evaulate"], "10.5 9.2 28.7": ["dewberries"], "-2.0 4.5 5.3": ["phytotherapy"], "-1.6 5.2 1.5": ["ombudspersons"], "0.1 15.4 6.1": ["parallelisms"], "8.9 9.0 0.8": ["gombeen"], "6.7 24.9 16.8": ["shmucks"], "4.9 17.0 9.2": ["possessives"], "6.8 5.8 4.7": ["improvisor"], "-0.8 -0.0 12.7": ["luan"], "0.9 16.2 -0.2": ["subsumption"], "-1.1 9.1 3.9": ["voidance"], "4.8 10.0 7.9": ["steeler"], "8.8 3.3 4.0": ["chloromethane"], "-4.5 6.4 4.4": ["convertion"], "5.3 5.4 -4.2": ["spricht"], "7.5 5.3 -0.5": ["heavied"], "3.5 11.4 7.6": ["amusia"], "11.9 6.8 18.7": ["calamine"], "-5.7 8.6 -3.7": ["discused"], "10.5 -1.1 6.9": ["growthin"], "18.8 10.3 18.7": ["fretboards"], "2.4 5.2 6.5": ["hoopskirts"], "19.2 12.8 19.4": ["boilersuit"], "3.4 9.4 20.9": ["recorked"], "9.0 5.4 29.5": ["golgappas"], "4.1 7.2 18.0": ["hybridising"], "16.8 2.5 8.4": ["prcent"], "15.0 11.5 17.0": ["pilaster"], "-0.6 16.4 14.1": ["inaudibility"], "11.3 5.1 2.1": ["dollers"], "8.9 2.6 9.2": ["unbylined"], "4.1 -0.6 3.2": ["avance"], "3.4 7.7 6.9": ["discogenic"], "2.3 20.2 6.5": ["connectability"], "4.8 6.8 15.2": ["ghe"], "9.1 11.5 16.4": ["swooningly"], "-1.8 7.5 -5.0": ["tolperisone"], "0.9 -1.6 0.5": ["railcards"], "22.0 7.9 19.7": ["dreadnaught"], "20.1 9.9 17.7": ["punkette"], "3.9 14.6 5.4": ["alliteratively"], "20.4 2.7 9.5": ["meteres"], "7.3 10.9 5.0": ["intensifed"], "-0.9 12.9 -2.1": ["comprimised"], "14.0 22.2 12.8": ["shuttlecraft"], "1.2 6.0 17.7": ["jayegi"], "-6.3 6.6 8.6": ["raz"], "7.7 11.7 4.0": ["rubico"], "7.8 -9.3 6.6": ["andnow"], "1.7 -0.1 14.0": ["fpc"], "6.4 3.4 10.8": ["boomlets"], "11.2 24.9 7.0": ["offboard"], "12.0 15.9 5.5": ["endianness"], "6.2 3.4 6.9": ["loanable"], "4.9 5.8 4.4": ["mukhiyas"], "-12.6 9.9 1.9": ["yana"], "13.7 4.2 14.3": ["athird"], "-6.1 11.2 2.8": ["spirometric"], "3.2 5.8 11.2": ["airheater"], "9.3 11.1 21.9": ["catfisherman"], "-1.0 0.3 10.1": ["noncompetitively"], "6.5 10.4 21.1": ["frostbit"], "-0.3 8.7 9.5": ["aplasia", "subnetwork"], "2.8 5.2 13.4": ["breaststoke"], "7.1 13.3 17.7": ["megaflood"], "0.4 0.3 -4.1": ["juridiction"], "18.4 -0.3 -4.2": ["maxdome"], "2.0 1.0 -0.2": ["airdashed"], "-3.1 9.1 15.9": ["isso"], "-1.8 -1.4 8.9": ["polyadenylation"], "-0.1 11.0 14.9": ["naal"], "0.3 20.4 4.5": ["thoe"], "16.6 8.5 19.7": ["unpressed"], "2.4 6.4 10.5": ["newcast"], "8.8 4.9 44.9": ["kampachi"], "3.5 9.5 7.2": ["adarsh"], "17.9 6.7 17.5": ["playmat"], "1.6 1.7 4.2": ["baketball"], "2.7 14.9 -0.6": ["ventanas"], "5.9 10.0 20.5": ["amonia"], "8.8 -4.1 13.4": ["tute"], "17.3 8.9 25.2": ["rafflesia"], "8.6 -3.2 13.1": ["angen"], "27.5 28.1 20.2": ["triffids"], "-1.4 10.0 8.5": ["yoginis"], "2.1 11.6 12.3": ["nesses"], "1.7 17.2 8.7": ["overprotectiveness"], "9.7 6.1 -4.6": ["revelead"], "-2.9 2.0 9.3": ["neraval"], "-6.0 7.8 8.1": ["locaton"], "-2.2 0.9 -1.9": ["appointement"], "3.9 7.3 17.1": ["mazaa"], "22.9 2.2 3.1": ["megafirm"], "12.2 3.1 -0.1": ["institue"], "25.0 7.3 11.8": ["stilettoed"], "11.1 11.5 10.6": ["resequence"], "-2.4 17.9 3.3": ["structuralists"], "8.0 22.6 13.2": ["unsatisfyingly"], "9.9 4.1 -0.9": ["verder"], "8.1 11.5 24.8": ["polyanthus"], "13.1 6.9 16.1": ["topclass"], "3.3 1.3 12.2": ["wirewound"], "10.6 6.7 19.6": ["giros"], "16.5 12.7 16.4": ["superfreak"], "12.7 29.7 19.3": ["nocked"], "16.8 13.2 4.1": ["quckly"], "6.3 -0.4 27.5": ["nua"], "15.8 11.1 11.5": ["ballsiness"], "3.5 27.1 10.3": ["nothingism"], "-0.3 24.2 8.4": ["inveterately"], "1.7 15.9 5.8": ["thriver"], "4.0 0.2 9.1": ["sportingbet"], "17.2 20.2 15.3": ["picadors"], "-8.9 4.6 13.0": ["rateables"], "-1.5 6.2 10.1": ["hematoxylin"], "4.4 0.2 9.6": ["avs"], "12.1 -1.2 5.7": ["principale"], "4.7 0.6 4.4": ["naphyrone"], "7.8 11.4 10.7": ["listbox"], "9.3 20.7 24.4": ["epiphyte"], "16.7 12.8 9.4": ["skidpan"], "-4.6 4.4 6.9": ["clientside"], "13.3 16.1 15.8": ["demark"], "1.8 14.7 4.5": ["vultured"], "17.0 11.7 1.1": ["spening"], "-4.7 21.3 3.6": ["strugle"], "-0.3 7.0 5.2": ["glycaemia"], "-8.1 6.9 -0.9": ["enaged"], "7.4 -0.8 -6.6": ["hydrofluoroalkane"], "5.0 20.3 11.4": ["derogatively"], "-4.4 9.3 6.3": ["romatic"], "5.5 6.7 13.4": ["uvea"], "6.8 19.1 32.4": ["outfish"], "-0.8 5.8 9.0": ["microdeletion"], "9.6 6.0 13.4": ["tubeset"], "8.0 11.7 6.1": ["emph"], "4.8 -2.9 -8.9": ["vicechancellor"], "19.8 3.1 18.2": ["multipanel"], "3.4 32.4 11.6": ["genocidally"], "8.8 2.1 11.7": ["lympics"], "17.4 -2.1 10.7": ["yodeller"], "9.1 12.9 18.2": ["integument"], "5.2 9.4 13.5": ["foodstock"], "-1.7 -2.9 -3.7": ["commissoner"], "6.8 9.3 6.2": ["theweekend"], "6.8 1.6 0.5": ["videostreaming"], "-3.0 12.0 7.4": ["cryptogenic"], "13.3 14.4 16.0": ["viroid"], "0.7 11.8 -1.1": ["referrence", "fatalaties"], "-3.7 2.7 7.3": ["ngl"], "15.0 -4.1 6.3": ["ageny"], "-2.3 -4.0 7.8": ["dywedodd"], "2.3 14.0 1.7": ["virotherapy"], "-4.3 6.2 8.9": ["perimetry"], "15.9 19.2 35.7": ["whaleboats"], "9.8 3.6 6.3": ["peruvian"], "12.6 -1.6 18.4": ["pianola"], "-2.2 -1.0 10.3": ["incepting"], "10.2 7.0 12.0": ["daffiness"], "5.1 15.2 19.9": ["serra"], "18.7 8.1 13.5": ["zoon"], "6.6 5.9 20.8": ["unflavoured"], "12.0 11.3 16.6": ["moby"], "-0.7 12.0 13.1": ["alabam"], "16.5 16.7 14.0": ["goombahs"], "4.9 7.8 13.7": ["gulaal"], "2.4 7.7 7.5": ["odorized"], "-7.8 12.7 1.6": ["rehman"], "3.9 10.2 12.9": ["cante"], "14.3 10.2 38.6": ["sotong"], "3.7 -6.4 11.8": ["qtz"], "-5.4 17.3 5.7": ["blanketly"], "-0.9 17.9 2.7": ["saddness"], "0.1 2.7 17.2": ["beni"], "10.9 8.2 27.3": ["woodiness"], "-5.9 4.0 10.1": ["dema"], "2.9 16.0 7.3": ["nonpersonal"], "12.6 20.0 8.5": ["infosphere"], "-4.3 4.3 11.9": ["parlez"], "5.8 12.4 14.2": ["contrapuntally"], "12.2 13.6 17.2": ["pund"], "4.1 14.8 5.9": ["huntley"], "0.9 -4.4 9.6": ["anta"], "22.8 27.8 8.3": ["superpowerful"], "14.1 1.0 -5.2": ["newsite"], "6.7 8.5 10.0": ["homocystinuria"], "-11.2 8.7 6.8": ["mitigatory"], "4.6 11.5 13.9": ["sporatic"], "9.8 -1.4 9.6": ["kuchipudi"], "19.5 9.5 24.4": ["graspers"], "-3.6 8.1 10.8": ["ojek"], "8.8 22.7 8.1": ["playside"], "5.1 4.4 26.5": ["nonvegetarians"], "12.5 12.2 3.1": ["booklight"], "-0.4 7.6 3.7": ["electroencephalographic"], "20.3 5.5 17.6": ["sideyard"], "20.5 13.5 20.5": ["skanked"], "15.8 5.9 16.4": ["mixings"], "17.6 8.8 9.2": ["steeplejacks"], "5.6 1.5 10.9": ["ghata"], "4.3 11.2 5.9": ["subpages"], "13.9 8.3 31.9": ["stewy"], "9.9 6.4 0.5": ["crossplatform"], "15.2 14.3 27.1": ["feist"], "3.7 7.8 15.3": ["urna"], "0.7 3.5 10.3": ["acidization"], "-4.1 3.8 6.2": ["soloistic"], "3.7 7.5 6.4": ["housholds"], "3.3 6.7 23.9": ["saskatoons"], "-3.8 15.6 9.2": ["beshert"], "3.3 15.1 14.7": ["fuc"], "-1.3 0.0 11.6": ["asso"], "5.4 -1.7 0.9": ["drophead"], "1.0 5.7 7.1": ["trafffic"], "10.3 4.7 17.0": ["lippie"], "8.0 5.9 52.9": ["linefish"], "-7.4 3.3 6.9": ["alw"], "10.3 20.5 9.2": ["tosspot"], "-4.6 7.9 6.5": ["uske"], "8.9 7.1 31.6": ["scuppernong"], "7.2 6.7 11.0": ["processless"], "0.8 15.1 6.9": ["pollwatchers"], "16.2 5.1 5.0": ["quangoes"], "12.1 6.8 2.1": ["connecters"], "1.6 9.2 15.3": ["koker"], "3.6 20.0 6.8": ["qurbani"], "9.1 6.6 4.7": ["diag"], "4.9 12.3 22.1": ["ouches"], "18.8 12.6 8.5": ["cricketainment"], "8.1 15.1 17.3": ["powerslams"], "-6.1 1.9 -3.5": ["tration"], "7.9 4.9 24.6": ["lebua"], "16.7 19.4 24.5": ["berberis"], "-7.0 13.4 1.2": ["commendatory"], "10.3 9.1 14.6": ["condyle"], "2.8 28.9 9.8": ["millennialism"], "2.5 5.1 6.1": ["outflux"], "12.9 -1.2 4.0": ["musicvideos"], "9.9 15.1 10.8": ["indys"], "-3.1 4.5 1.0": ["divulgation"], "12.6 8.2 19.6": ["baggin"], "20.9 13.1 28.4": ["wattled"], "-5.5 -1.5 9.4": ["karyotypes"], "18.7 8.6 26.2": ["manti"], "-0.1 11.5 15.3": ["bhari"], "14.4 12.0 28.6": ["izakayas"], "4.4 9.7 0.1": ["sinewave"], "2.2 0.5 7.0": ["futureresults"], "6.0 6.5 22.9": ["makahiki"], "-0.7 0.2 -8.7": ["resutls"], "9.8 10.4 5.0": ["clickbank"], "8.3 27.5 5.2": ["derange"], "1.9 13.4 8.6": ["hematization"], "-6.7 13.1 -1.5": ["accompaniers"], "6.9 9.3 19.4": ["brassinosteroids"], "4.2 2.9 5.9": ["steamflood"], "11.0 14.3 24.7": ["deoxygenated"], "5.2 -0.1 7.7": ["thevalue"], "13.4 29.2 31.1": ["nestmates"], "-5.5 0.6 13.0": ["informals"], "-0.8 11.0 0.4": ["appointor"], "9.3 26.7 3.0": ["fauji"], "4.7 25.9 0.9": ["harbourers"], "9.3 8.1 15.2": ["tahs"], "9.6 19.4 7.8": ["overhanded"], "7.4 20.9 12.0": ["deleteriously"], "4.7 -1.2 -0.6": ["recogntion"], "8.9 4.0 14.4": ["gayle"], "12.0 3.2 20.4": ["sandmining"], "4.4 17.7 3.8": ["spaser"], "-9.0 -1.4 -5.3": ["assisstant"], "1.7 10.6 12.7": ["pretreatments"], "3.4 11.3 10.3": ["trie"], "1.7 11.6 0.7": ["impassion"], "-3.7 -1.6 2.9": ["oversubscribing"], "11.2 24.8 6.7": ["hexing"], "4.5 3.5 10.7": ["ragamalika"], "0.7 5.0 15.0": ["minesites"], "23.2 12.5 20.4": ["fratboys"], "4.8 23.9 15.0": ["jnana"], "14.6 -7.4 -13.1": ["serivces"], "9.3 17.1 9.7": ["finitely"], "5.4 -8.4 5.9": ["volte"], "12.1 9.0 20.0": ["degreased"], "-0.4 24.6 5.5": ["conversating"], "-1.6 15.4 12.5": ["relativly"], "-6.4 9.4 7.4": ["homas"], "3.1 13.9 15.8": ["muhibbah"], "3.8 -3.4 -2.6": ["availbale"], "14.7 10.6 7.7": ["broswer"], "18.9 6.9 22.7": ["iroko"], "12.9 12.9 3.9": ["decompiling"], "6.1 10.3 2.1": ["hisfirst"], "1.6 -1.1 -7.7": ["respresenting"], "12.1 30.4 17.1": ["libruls"], "6.0 17.5 5.1": ["interupts"], "2.6 10.2 2.4": ["folgende"], "24.7 13.4 13.7": ["leafblower"], "5.3 12.7 8.3": ["supertalented"], "6.8 28.5 6.0": ["suzerain"], "18.1 11.4 31.0": ["brownest"], "-11.5 2.8 -0.3": ["caddieing"], "6.0 7.3 12.0": ["voit"], "14.0 2.4 4.0": ["strugling"], "7.6 6.0 28.1": ["feijoas"], "-2.8 21.1 11.1": ["wholeheartedness"], "14.2 6.2 3.0": ["medicity"], "0.5 1.3 5.6": ["estacodes"], "2.3 4.5 14.0": ["convalescents"], "4.9 4.4 13.1": ["actressy"], "2.0 11.8 -3.8": ["controle"], "2.1 8.3 11.0": ["sasabihin"], "2.5 8.8 -4.1": ["acce"], "4.2 13.9 10.8": ["unathorized"], "10.3 14.7 19.1": ["rushin"], "-4.8 7.5 11.3": ["patna"], "12.7 18.7 4.9": ["obssession"], "9.0 3.9 7.7": ["deliquencies"], "9.7 24.5 4.0": ["cyberweapon"], "11.0 12.1 17.4": ["reassorted"], "6.3 4.7 10.9": ["timespreads"], "10.4 -0.5 7.6": ["bienvenidos"], "10.7 13.6 11.8": ["vielen"], "-1.5 8.7 13.4": ["utilitymen"], "12.7 12.9 19.1": ["shunto"], "6.6 4.6 12.1": ["ipswich"], "9.1 -0.5 11.5": ["farmwife"], "14.8 17.4 19.3": ["ornithischians"], "15.0 17.0 23.7": ["microhabitats"], "15.2 11.2 27.7": ["honeyeater"], "0.7 4.1 18.9": ["batchelor"], "17.5 6.1 29.5": ["cordyline"], "12.0 13.6 9.2": ["unban"], "7.5 1.4 -8.5": ["cathlab"], "10.2 4.3 17.9": ["torcs"], "14.0 13.4 8.1": ["officialssaid"], "10.2 13.7 15.5": ["icosahedral"], "9.2 11.3 22.4": ["pollyanna"], "-6.6 18.2 9.6": ["kf"], "17.8 3.3 12.2": ["bargins"], "19.9 2.0 6.4": ["agrobusiness"], "1.0 4.3 6.7": ["erscheint"], "-1.3 5.6 7.5": ["sten"], "12.7 1.7 1.6": ["champi"], "-4.3 3.1 -3.4": ["halala"], "3.9 0.6 5.6": ["toghether"], "8.7 4.2 6.6": ["calciopoli"], "8.6 5.1 11.0": ["washeteria"], "2.4 6.2 6.5": ["emittance"], "3.5 1.0 9.4": ["bobrauschenbergamerica"], "1.5 10.1 7.0": ["crosscultural"], "9.7 18.8 44.5": ["fisherpeople"], "3.9 20.5 5.9": ["thinkings"], "30.0 5.2 4.1": ["bbi"], "10.1 12.9 0.3": ["izes"], "-2.0 -2.0 11.0": ["fairboard"], "4.0 15.9 4.1": ["youngters"], "-7.0 9.0 5.7": ["laparoscopies"], "-2.3 15.9 9.5": ["adu"], "14.2 22.1 15.3": ["spreadin"], "2.3 4.7 17.7": ["siri"], "1.3 -1.8 15.2": ["subbasin"], "-6.1 13.8 2.6": ["aqidah"], "5.2 10.1 20.4": ["orographic"], "12.9 2.6 14.6": ["tamara"], "4.1 1.1 4.5": ["mugam"], "15.5 3.9 21.2": ["breeks"], "9.5 7.6 11.3": ["replumbed"], "-0.7 -9.9 0.5": ["coogi"], "4.8 23.0 13.5": ["intesity"], "-5.5 18.6 7.3": ["youngness"], "-0.1 19.5 5.0": ["debilitatingly"], "5.7 13.2 7.0": ["embracers"], "2.8 21.9 1.8": ["appologies"], "15.8 29.8 23.8": ["swordsmith"], "20.8 5.8 24.3": ["knackwurst"], "12.5 14.1 7.2": ["pieta"], "-0.3 -2.6 -2.5": ["eprescribing"], "1.8 -1.2 35.1": ["nonbreeding"], "0.6 10.8 4.5": ["presidenta"], "10.1 1.5 7.4": ["snapbacks"], "13.9 -5.0 27.2": ["edam"], "12.0 7.5 29.7": ["nestboxes"], "2.5 6.6 10.1": ["contast"], "-0.0 2.3 16.7": ["chini"], "3.8 4.5 6.5": ["microdebrider"], "1.4 -3.2 -4.3": ["isued"], "-4.3 1.2 -1.7": ["superannuating"], "9.1 -3.1 7.7": ["increa"], "3.1 9.0 2.1": ["onroad"], "-10.3 -0.6 8.4": ["leachables"], "6.2 21.9 -1.4": ["thiers"], "13.2 3.1 11.4": ["peerperform"], "1.7 13.6 8.5": ["taget"], "11.0 22.1 5.4": ["foneros"], "13.1 33.2 9.8": ["simplemindedness"], "16.5 6.1 43.7": ["sargo"], "-1.7 14.7 3.8": ["congressmember"], "6.2 15.7 11.7": ["sendiri"], "-12.0 -2.4 8.5": ["fos"], "-0.6 12.6 12.0": ["acidulous"], "4.3 10.3 17.7": ["wateriest"], "18.8 -2.4 18.7": ["svelt"], "8.3 1.8 29.5": ["makhani"], "5.2 12.3 6.1": ["truckdrivers"], "1.3 11.8 6.1": ["unimmunised"], "6.7 11.2 22.5": ["waw"], "0.1 10.1 13.7": ["helmswoman"], "-2.6 -5.1 11.4": ["pih"], "15.2 13.9 18.7": ["troweling"], "-1.5 6.5 14.1": ["greensome"], "2.4 13.8 18.6": ["crontab"], "13.5 0.8 7.7": ["northest"], "12.3 11.6 12.9": ["marquez"], "14.0 15.2 3.9": ["shooted"], "-4.6 10.2 13.1": ["passaging"], "-8.4 4.1 10.0": ["excisional"], "5.7 -6.8 10.4": ["supersaver"], "5.8 15.2 5.8": ["perilune"], "0.4 9.5 2.1": ["requisitionists"], "8.8 7.9 6.4": ["nanowatts"], "9.1 21.6 13.1": ["hysterias"], "6.0 17.5 19.1": ["jima"], "-1.8 17.1 1.8": ["philosopy"], "-3.8 1.3 2.5": ["whelmingly"], "-2.9 11.2 20.6": ["gregg"], "12.6 8.6 13.2": ["toilettes"], "-1.6 3.3 11.9": ["drut"], "12.4 15.1 -3.5": ["connectively"], "10.8 6.0 34.9": ["cicchetti"], "11.0 0.8 15.6": ["riverwalks"], "10.0 12.0 18.1": ["bottommost"], "14.8 -2.9 11.0": ["polybagged"], "2.1 6.0 18.4": ["curers"], "2.1 11.4 -1.0": ["ideations"], "10.6 -0.6 5.9": ["craftworkers"], "11.9 9.6 14.0": ["wonkiest"], "14.5 -0.4 5.7": ["dispaly"], "-2.5 14.5 33.9": ["anterless"], "10.9 1.3 10.4": ["toothcomb"], "3.6 16.5 9.0": ["outyear"], "17.6 17.7 14.0": ["motorize"], "-1.9 -4.9 1.4": ["noti"], "12.5 -0.4 21.4": ["wallaroos"], "-2.2 10.3 8.2": ["numerologically"], "11.2 8.8 14.2": ["catnapped"], "6.6 24.0 12.2": ["retaliator"], "19.7 14.4 26.0": ["spiles"], "12.7 1.3 20.4": ["cooldrinks"], "8.4 21.1 14.4": ["fucktard"], "15.5 7.3 18.7": ["unfancy"], "9.5 6.1 14.1": ["benzaldehyde"], "16.9 32.7 9.5": ["rappeling"], "9.1 10.9 9.0": ["aneath"], "12.5 4.9 8.1": ["moonball"], "-3.0 -1.4 -2.5": ["foras"], "13.6 13.5 5.3": ["trackwheel"], "5.0 12.1 7.8": ["tawaif"], "-1.0 6.3 3.7": ["antidepressive"], "-0.4 12.0 18.5": ["protags"], "20.8 6.1 26.8": ["birchwood"], "10.3 1.2 14.6": ["cata"], "4.5 8.0 24.2": ["latifolia"], "12.2 10.0 38.4": ["bigheads"], "-6.7 3.6 1.9": ["dto"], "6.1 13.8 4.6": ["familliar"], "0.6 0.2 12.8": ["benton"], "5.9 12.5 9.5": ["translocates"], "10.1 -0.2 8.0": ["thiophene"], "2.1 1.1 8.4": ["asics"], "11.9 10.9 14.1": ["gothamist"], "11.9 13.1 5.6": ["radaronline"], "4.2 2.2 11.6": ["pacework"], "10.0 6.8 13.9": ["squadra"], "5.3 2.4 10.2": ["electrodialysis"], "0.9 4.2 3.3": ["alledgely"], "7.9 -6.5 11.1": ["afive"], "14.5 11.3 5.2": ["insead"], "17.2 10.4 10.1": ["multivehicle"], "-7.6 3.1 -1.1": ["asistant"], "2.3 1.8 12.8": ["sanang"], "0.9 8.7 9.2": ["sinfonia"], "7.4 8.0 12.1": ["enoug"], "3.2 7.7 0.0": ["europa"], "6.6 9.6 12.0": ["peolple"], "-0.7 7.0 9.7": ["senteced"], "3.4 8.5 17.4": ["kabataan"], "10.4 0.0 13.2": ["passcards"], "9.3 11.0 12.3": ["shadily"], "-6.2 11.5 0.5": ["questionability"], "-0.6 10.9 -1.0": ["disclosers"], "5.9 8.0 8.2": ["cappela"], "15.7 22.4 10.6": ["hyprocrisy"], "-0.6 5.2 20.3": ["multidecadal"], "1.3 -0.3 9.4": ["auc"], "17.7 17.6 19.9": ["supercontinents"], "11.7 14.6 15.6": ["buffest"], "2.7 -4.2 6.2": ["thermage"], "7.4 16.2 11.4": ["burnley"], "0.9 7.9 11.7": ["tillana"], "9.8 8.5 6.9": ["shoutbox"], "7.8 5.5 11.4": ["salicin"], "5.3 1.6 4.8": ["dahs"], "0.4 7.9 11.5": ["nonlegislative"], "1.6 18.3 1.7": ["syaing"], "-0.2 2.5 17.0": ["pavan"], "1.1 -0.1 11.7": ["couleurs"], "10.2 7.5 28.5": ["thit"], "15.5 -1.0 17.2": ["stalefish"], "2.4 5.3 21.8": ["andrographis"], "1.5 -0.4 7.5": ["clefting"], "3.5 10.8 7.5": ["malafides"], "2.6 19.1 3.3": ["democrate"], "25.8 3.5 6.0": ["largets"], "2.8 8.9 8.9": ["unpressurised"], "4.9 9.9 10.1": ["sentido"], "-2.9 6.4 2.8": ["proclaimation"], "10.3 13.1 7.5": ["pasenger"], "6.5 9.5 10.4": ["bery"], "10.9 2.1 15.6": ["kavadis"], "9.8 -0.5 39.9": ["kielbasi"], "7.7 12.1 9.6": ["rapey", "buid"], "15.2 26.4 17.5": ["demoness"], "-4.3 18.6 6.0": ["resourse"], "6.7 22.9 10.5": ["goriness"], "3.9 4.2 9.8": ["chillaxin"], "7.0 10.3 27.8": ["daun"], "1.8 5.2 10.3": ["casemix"], "9.0 11.1 9.6": ["finden"], "12.9 9.3 16.6": ["raunchily"], "14.6 8.2 11.4": ["sawzall"], "4.6 11.3 17.8": ["chometz"], "11.1 -2.5 1.0": ["ngpay"], "11.8 9.7 11.9": ["westies"], "18.2 16.1 26.8": ["kistka"], "-0.8 2.5 5.8": ["northsouth"], "1.4 5.3 13.7": ["oncomodulin"], "1.3 10.2 9.6": ["onour"], "10.2 18.7 17.1": ["karsts"], "0.6 18.0 11.1": ["behinder"], "9.7 20.1 12.8": ["snorters"], "0.4 -5.4 -6.2": ["sumit"], "-1.3 2.9 -2.2": ["stereochemistry"], "5.3 13.7 1.9": ["irksomely"], "6.4 13.2 14.0": ["spinarama"], "3.9 7.6 12.0": ["saare"], "6.9 29.8 7.9": ["impostures"], "-2.0 8.2 -1.8": ["plyed"], "14.6 13.2 8.8": ["babylon"], "-1.7 10.0 3.9": ["generis"], "13.6 4.1 22.3": ["crape"], "18.6 4.2 10.7": ["marketmaker"], "6.9 -9.0 8.6": ["monterey"], "-3.2 0.6 5.2": ["murs"], "8.6 3.5 11.3": ["pesa"], "12.4 10.8 4.6": ["buzzphrase"], "10.6 -6.6 -2.9": ["otcqx"], "15.3 7.5 13.3": ["supbrime"], "-6.4 18.4 2.9": ["couldhave"], "-4.7 22.7 -1.6": ["separative"], "4.7 -4.8 2.8": ["bove"], "8.7 3.8 12.7": ["divied"], "3.6 9.9 12.2": ["accout"], "7.4 14.5 12.0": ["connectome"], "2.7 3.6 0.5": ["fdba"], "14.6 19.6 5.3": ["unfo"], "2.7 -1.0 5.8": ["sitaxsentan"], "8.9 12.4 6.5": ["alchoholic"], "8.2 8.1 11.6": ["tling"], "6.7 14.1 15.5": ["oxycholesterol"], "11.6 8.5 10.2": ["mitted"], "6.9 8.0 7.3": ["unscanned"], "12.6 4.5 3.2": ["compra"], "13.9 13.0 28.1": ["kefta"], "11.4 -0.6 2.7": ["thefull"], "-0.6 -3.7 4.4": ["liq"], "-2.8 2.1 -1.1": ["inotropes"], "9.8 12.3 8.9": ["houseproud"], "23.0 19.5 10.9": ["cannibalises"], "-1.8 3.2 15.3": ["preponing"], "11.4 8.8 15.6": ["cofee"], "-0.8 10.4 8.8": ["tomy"], "4.3 -2.1 7.1": ["lec"], "18.6 20.5 12.0": ["reconceiving"], "9.6 22.9 -2.7": ["telegraphers"], "9.2 6.3 18.6": ["pung"], "5.6 7.3 2.1": ["hymning"], "19.3 9.0 15.8": ["mirdle"], "6.8 5.7 8.7": ["veshti"], "7.5 27.6 16.2": ["imaginably"], "-1.3 28.5 7.3": ["subcommander"], "11.0 4.9 28.7": ["sempervirens"], "14.0 11.9 30.5": ["bushbaby"], "18.7 2.5 6.5": ["theconstruction"], "13.7 11.6 13.9": ["jishuku"], "10.4 9.0 17.1": ["scena"], "0.0 3.4 4.0": ["bieten"], "3.7 4.4 11.2": ["ux"], "12.7 0.9 32.3": ["boursin"], "3.4 19.6 1.2": ["playcallers"], "6.7 12.3 11.7": ["hypnagogic"], "2.7 6.1 7.5": ["aguero"], "13.0 23.8 37.7": ["chironomids"], "11.3 11.5 8.1": ["famouse"], "8.1 5.8 17.2": ["quartette"], "16.0 15.3 22.6": ["wolfsbane"], "16.3 23.6 23.9": ["unconcernedly"], "16.5 12.0 21.1": ["spectactors"], "12.1 15.4 15.6": ["nerdly"], "11.6 1.5 19.6": ["sumi"], "17.6 10.7 11.7": ["sciency"], "26.8 19.8 8.6": ["moonbase"], "14.8 15.0 14.6": ["sandpapering"], "18.9 12.4 10.6": ["eyebolts"], "11.1 6.6 20.8": ["diddley"], "5.5 9.9 10.3": ["laxmen"], "7.0 8.3 12.1": ["pwer"], "-1.8 11.7 9.6": ["eruditely"], "-3.6 -2.9 13.8": ["cari"], "17.7 9.1 23.9": ["gaura"], "1.3 18.2 11.9": ["explainations"], "-2.4 23.4 1.9": ["particularize"], "-4.4 -0.2 3.1": ["underexpressed"], "10.7 4.3 19.8": ["dok"], "4.2 11.1 5.3": ["miniutes"], "6.6 15.6 11.5": ["goverenment"], "13.1 4.4 5.3": ["recladding"], "6.3 2.4 -9.0": ["conferene"], "-4.2 12.5 9.7": ["senseis"], "1.1 6.3 13.0": ["jax"], "5.5 1.9 7.8": ["slideouts"], "2.0 33.7 1.9": ["intriguer"], "14.6 8.9 22.6": ["dovecotes"], "4.7 13.2 8.0": ["torcher"], "11.6 11.4 8.1": ["embalmment"], "9.6 16.6 18.3": ["absurdness"], "10.1 -0.7 0.9": ["cablecom"], "6.4 12.1 21.8": ["smellers"], "0.7 11.0 13.9": ["dysplasias"], "-0.3 6.8 10.7": ["spongiform"], "-0.2 1.8 -2.2": ["dexlansoprazole"], "15.8 19.2 13.6": ["sirree"], "8.0 1.2 7.8": ["acciones"], "12.5 7.7 11.9": ["arachnologist"], "2.1 6.1 4.2": ["conformer"], "8.1 8.0 8.7": ["megaselling"], "1.3 -2.9 0.4": ["audiometry"], "14.8 12.7 13.6": ["unclasping"], "10.7 18.8 9.0": ["unconstitional"], "3.4 23.7 10.1": ["blamer"], "2.0 9.0 5.6": ["schoolmasterly"], "-8.5 10.7 6.4": ["lackof"], "-2.1 18.0 9.3": ["exs"], "-6.4 13.0 -2.8": ["antituberculosis"], "13.4 7.7 10.4": ["wipeable"], "18.4 2.7 26.2": ["muenster"], "6.0 0.4 9.3": ["osa"], "21.9 23.2 20.2": ["birdmen"], "5.7 22.6 6.9": ["combatative"], "17.6 10.0 19.3": ["jupiter"], "9.2 8.5 -2.1": ["arow"], "8.2 22.4 6.0": ["rapha"], "21.8 0.8 7.7": ["dereg"], "1.9 -3.6 6.9": ["ouest"], "15.7 3.8 15.7": ["artiest"], "22.3 -3.3 5.3": ["adverstising"], "10.0 20.3 0.7": ["criticizers"], "4.4 -1.1 10.5": ["minicomics"], "10.0 20.7 13.0": ["cusswords"], "4.8 10.5 3.6": ["quasijudicial"], "8.9 9.5 14.9": ["arou"], "-2.2 0.2 8.4": ["megaschools"], "5.3 20.2 5.0": ["unstatesmanlike"], "4.6 17.4 12.5": ["antinomy"], "7.1 17.6 15.7": ["suberin"], "5.7 10.9 8.3": ["verdad"], "-6.1 3.6 9.5": ["shortsop"], "14.6 15.1 13.0": ["micromachine"], "0.8 9.5 0.1": ["therace"], "-6.8 -1.6 2.8": ["idenitified"], "14.8 6.5 6.4": ["ciy"], "19.4 16.0 14.4": ["enron"], "4.3 3.8 2.1": ["videoscopes"], "7.3 -0.4 10.0": ["revenus"], "12.9 0.0 7.9": ["anks"], "-1.0 9.6 0.9": ["definitization"], "3.9 -6.4 -3.5": ["unavailble"], "6.2 25.1 6.8": ["vollies"], "5.5 20.5 3.4": ["armalite"], "14.8 -0.8 -1.9": ["launche"], "3.1 8.9 5.5": ["prochlorperazine"], "8.2 14.0 4.7": ["oppposed"], "3.1 9.7 33.9": ["catchables"], "14.6 4.9 0.4": ["reserachers"], "10.3 8.9 15.9": ["griminess"], "20.7 16.4 5.1": ["monumentous"], "11.6 13.4 3.3": ["mediatic"], "15.6 2.8 23.5": ["kukui"], "0.5 28.2 20.6": ["hyperbolize"], "-0.2 13.9 9.2": ["physiographic"], "8.8 7.7 19.1": ["intermittant"], "18.3 17.4 9.4": ["tachyon"], "-6.2 12.6 -0.4": ["crossexamination"], "1.1 5.5 -2.6": ["volving"], "12.2 8.4 20.2": ["nargileh"], "9.1 15.7 17.9": ["linky"], "6.3 7.6 14.7": ["jmh"], "-7.0 4.1 -2.8": ["apointment"], "15.7 10.3 12.3": ["mpd"], "-3.9 14.2 7.5": ["upregulating"], "6.5 14.1 4.5": ["shopability"], "2.1 8.8 3.2": ["neurosteroid"], "-5.4 -10.3 11.1": ["tutition"], "11.1 4.4 -0.8": ["mismarkings"], "-4.9 -7.1 6.3": ["mcgs"], "10.1 13.0 11.1": ["centurymaker"], "5.8 4.6 6.7": ["skimpiness"], "2.5 1.6 3.3": ["compliers"], "16.4 8.3 12.9": ["pokechecked"], "8.2 4.0 13.3": ["veteranarian"], "0.2 9.5 4.8": ["heirless"], "14.9 -0.0 9.5": ["facias"], "10.9 9.5 6.3": ["interestrates"], "10.3 12.0 5.5": ["visibile"], "10.4 4.4 8.1": ["cessed"], "13.5 10.4 33.1": ["siskin"], "-3.2 -2.9 8.4": ["mohr"], "13.8 -0.5 19.5": ["parkwide"], "12.8 6.6 11.7": ["slakes"], "6.9 20.9 1.7": ["adminisration"], "-4.9 1.0 6.2": ["drangpon"], "-2.1 9.7 13.0": ["storability"], "7.1 13.7 -0.4": ["emulative"], "-4.9 13.9 8.2": ["opin"], "1.8 6.4 8.3": ["equinus"], "0.8 1.4 8.9": ["downcounty"], "6.1 4.1 6.5": ["fenofibrates"], "7.6 4.0 7.3": ["especally"], "11.2 10.9 22.7": ["riverbottom"], "6.8 -1.5 16.8": ["deng"], "18.5 0.7 -4.2": ["reenergised"], "5.1 -3.0 5.5": ["gasprices"], "9.4 20.1 11.2": ["ungenerously"], "-8.6 -2.8 -3.1": ["gradute"], "14.4 12.4 15.5": ["feudin"], "-7.4 5.5 0.9": ["sanad"], "5.5 -10.9 8.4": ["polyisobutylene"], "16.4 26.3 5.1": ["sixaxis"], "4.9 5.9 6.7": ["meilleur"], "-1.8 10.7 10.2": ["intellisense"], "4.3 10.8 15.8": ["banna"], "4.2 9.8 12.5": ["socionomics"], "8.5 6.2 11.5": ["tourmament"], "4.2 6.8 -0.7": ["pred"], "6.7 0.1 0.2": ["babygirl"], "5.2 13.3 15.7": ["neurofibroma"], "3.4 12.2 3.3": ["mamu"], "7.3 -6.6 0.8": ["polyketals"], "1.9 8.7 12.7": ["particpant"], "3.8 4.2 7.0": ["cutsheet"], "14.1 8.8 16.2": ["cappucinos"], "1.2 23.0 7.2": ["missiological"], "9.9 -0.4 -4.3": ["dme"], "1.8 34.2 4.5": ["wargear"], "-1.1 5.3 14.0": ["trochanteric"], "13.5 10.8 19.3": ["smashin"], "17.1 19.8 33.6": ["treefrogs"], "-2.8 5.2 7.3": ["similares"], "7.8 -0.3 4.6": ["hydroxylated"], "3.3 2.8 1.6": ["pressor"], "-8.2 5.1 7.5": ["routability"], "11.5 4.6 6.7": ["organometallics"], "15.1 3.6 12.4": ["vivant"], "2.0 11.9 6.1": ["someon"], "8.0 5.6 5.7": ["existant"], "9.8 11.6 11.4": ["aristocratically"], "-0.6 2.1 -2.3": ["hiree"], "10.7 24.7 2.0": ["radicalness"], "1.3 14.2 7.2": ["emigrations"], "23.4 34.4 9.6": ["wookies"], "2.0 8.7 14.6": ["naanbais"], "17.5 6.6 26.9": ["scoopable"], "-0.9 10.4 5.5": ["sufficently"], "20.7 8.7 27.1": ["dewlap"], "-0.5 6.6 20.2": ["canaryseed"], "7.7 14.9 41.4": ["prefish"], "24.8 12.4 4.9": ["corportate"], "-1.4 15.2 -2.8": ["wouls"], "4.0 -0.0 12.5": ["momentoes"], "4.1 13.5 14.0": ["thosands"], "11.6 -6.6 9.1": ["sistemi"], "-5.5 1.7 6.6": ["talas"], "6.2 7.7 10.6": ["blendable"], "21.8 5.0 12.7": ["toodle"], "14.0 4.2 7.9": ["permatanned"], "1.7 3.8 -3.0": ["bmcoforum"], "-5.6 22.7 2.9": ["ijma"], "0.5 2.4 13.8": ["loams"], "2.9 -1.1 5.2": ["apc"], "10.3 5.1 35.9": ["karahi"], "1.6 12.7 6.5": ["yogas"], "5.2 1.9 17.5": ["affectedly"], "-0.7 11.5 14.6": ["usap"], "3.8 14.8 19.1": ["bacteriocins"], "-1.0 -0.5 4.8": ["itals"], "-0.9 19.2 10.5": ["chag"], "-2.7 20.5 9.8": ["defenisve"], "12.6 13.6 3.8": ["antiferromagnets"], "6.7 9.8 7.9": ["autonomics"], "16.8 -2.0 12.9": ["biopharmas"], "3.9 15.2 9.5": ["tches"], "15.7 6.4 23.2": ["dango"], "6.8 9.2 10.0": ["gustiest"], "12.2 3.8 5.1": ["preannouncing"], "14.2 10.5 22.6": ["locavorism"], "-1.0 9.6 10.8": ["invision"], "17.4 13.2 5.8": ["brainboxes"], "2.9 -0.5 0.9": ["spotcheck"], "1.5 11.8 1.4": ["mohtasib"], "5.4 -3.1 -3.1": ["isdesigned"], "6.4 16.9 9.7": ["soberingly"], "-0.0 8.4 18.6": ["nonpotable"], "3.1 10.2 13.0": ["bourgie"], "7.5 18.6 10.1": ["guyness"], "-3.5 10.7 4.2": ["kilonser"], "12.0 7.5 7.6": ["chromotherapy"], "16.1 14.2 11.7": ["guyed"], "5.4 -0.1 5.4": ["ofe"], "23.8 20.2 22.8": ["wingspread"], "4.8 4.9 16.3": ["centry"], "7.3 15.2 1.9": ["sainik"], "14.7 13.5 12.8": ["tremours"], "6.0 12.0 12.4": ["gesundheit"], "2.8 13.9 12.7": ["myajc"], "1.4 4.7 5.0": ["unsuprisingly"], "11.1 1.7 11.9": ["polyacrylate"], "13.5 -3.9 6.7": ["terrabyte"], "-0.2 12.3 6.7": ["incompliant"], "14.2 10.4 9.3": ["megamusical"], "8.2 10.4 3.9": ["landcruiser"], "0.7 -2.4 14.6": ["barato"], "15.1 6.1 2.7": ["imax"], "-8.3 4.1 5.3": ["ural"], "16.7 6.5 14.1": ["humper"], "14.8 17.6 0.3": ["aparthied"], "13.0 14.3 26.5": ["androgynously"], "5.9 14.9 16.7": ["sphingomyelin"], "4.7 8.8 2.5": ["formlines"], "8.0 14.4 25.4": ["chupa"], "4.6 13.5 19.0": ["swertres"], "7.5 4.6 7.4": ["didjeridoo"], "-6.3 7.2 4.1": ["makethe"], "10.6 20.1 13.2": ["purush"], "10.0 10.1 13.0": ["myraid"], "12.3 7.3 30.7": ["ilex"], "-4.7 14.8 4.0": ["glycopeptide"], "21.7 -6.8 8.3": ["plannned"], "4.0 2.9 9.4": ["banque"], "9.2 13.2 9.3": ["peptoid"], "-5.4 -3.4 -1.5": ["sistant"], "10.5 -5.2 -0.0": ["peermusic"], "10.9 17.2 7.6": ["preferance"], "20.0 14.1 10.8": ["tattering"], "-5.1 3.7 7.9": ["thatshe"], "1.3 3.7 1.9": ["autocatalytic"], "16.4 3.3 7.7": ["prepubescents"], "-1.1 11.8 22.4": ["didnae"], "3.8 -7.0 -0.8": ["yearin"], "6.2 -3.3 -2.0": ["topurchase"], "3.4 -9.8 -4.8": ["biopharmaceutics"], "8.1 1.4 10.5": ["thestart"], "-0.9 2.8 9.4": ["obe"], "7.5 21.1 2.6": ["rectenna"], "11.4 19.8 10.6": ["burm"], "6.0 7.9 7.3": ["stongest"], "11.5 9.3 9.0": ["qld"], "17.6 -5.4 9.1": ["apre"], "16.7 14.0 26.3": ["whapped"], "4.9 6.6 18.2": ["cinta"], "13.2 17.7 17.5": ["piledrive"], "2.1 9.7 1.5": ["fida"], "10.6 -9.0 -1.7": ["recentl"], "7.1 10.3 15.2": ["ipsum"], "12.8 7.3 8.0": ["contraversy"], "-1.8 0.0 -1.1": ["workingwith"], "9.1 -2.7 13.5": ["semiabstract"], "20.8 10.7 20.8": ["vigas"], "-4.2 7.6 -0.7": ["excellents"], "-3.7 6.1 1.4": ["suresh"], "8.9 8.5 5.8": ["funnybones"], "9.9 4.9 13.1": ["comed"], "7.6 9.2 21.7": ["scaevola"], "7.6 1.3 8.5": ["organiza"], "6.7 8.4 0.0": ["spectro"], "5.1 15.8 -3.5": ["deservers"], "4.8 16.1 19.4": ["disher"], "1.4 23.0 3.5": ["henious"], "18.0 7.1 15.1": ["pinscher"], "8.3 25.3 18.4": ["questers"], "5.7 11.5 12.7": ["sulkiness"], "2.7 15.1 0.6": ["jeepmen"], "3.5 15.9 9.9": ["fifers"], "2.0 10.9 11.2": ["basemaps"], "5.6 9.9 5.0": ["unprovided"], "4.8 13.5 7.5": ["verbosely"], "7.9 2.6 6.1": ["footall"], "14.2 5.2 -9.2": ["magnetoresistive"], "-2.2 -5.2 4.6": ["lasvegas"], "11.0 11.1 9.1": ["slingbox"], "3.0 4.8 7.2": ["atte"], "-4.6 -5.1 -4.0": ["consultive"], "9.0 6.7 5.5": ["zygomatic"], "4.0 11.0 3.7": ["superscripts"], "5.4 11.4 11.6": ["unintelligibility"], "5.7 4.0 7.7": ["sollten"], "6.8 8.8 0.7": ["dangerzone"], "15.8 6.8 11.5": ["takea"], "15.3 17.4 5.3": ["evetually"], "2.1 -2.4 12.1": ["nutrigenomic"], "2.6 7.9 0.8": ["cadenas"], "5.7 13.2 9.3": ["degee"], "-5.4 6.9 6.6": ["rheumatological"], "-0.9 23.9 0.8": ["instrumentalize"], "12.7 -1.5 -2.1": ["officies"], "16.9 17.9 11.2": ["elfs"], "4.4 17.7 4.0": ["institutionality"], "-2.4 22.4 2.5": ["apologizer"], "-2.0 4.0 3.0": ["innngs"], "9.9 24.9 15.7": ["scuzzball"], "20.8 20.2 10.1": ["puppeteered"], "4.7 10.4 8.5": ["izz"], "16.7 20.5 18.1": ["titanically"], "6.7 13.8 18.4": ["prewash"], "12.1 4.5 18.6": ["brasiliensis"], "-2.0 8.5 16.9": ["journeyperson"], "10.1 16.4 14.5": ["monosyllable"], "11.3 5.4 15.5": ["giddyap"], "18.8 13.0 22.8": ["orangs"], "17.2 13.2 1.3": ["overwhemingly"], "-7.1 1.5 -0.9": ["saide"], "3.3 17.6 3.9": ["bereaving"], "-1.3 -7.5 -2.1": ["febbraio"], "15.2 10.8 29.8": ["khachapuri"], "11.9 4.4 24.3": ["limon"], "11.5 17.2 14.5": ["tombaroli"], "-2.8 0.9 1.7": ["dele"], "6.2 8.0 25.7": ["paddleboarder"], "15.4 20.7 10.4": ["bioshock"], "-1.5 15.8 12.3": ["ayin"], "-3.2 13.7 4.9": ["smpjcu"], "16.3 28.2 5.9": ["tyrannizes"], "11.2 -1.4 5.7": ["tabletting"], "14.3 6.5 15.3": ["cringy"], "6.1 -3.6 6.7": ["diethylstilbestrol"], "-4.3 11.6 11.8": ["newsrelease"], "4.0 5.3 23.2": ["spikelets"], "13.3 5.9 10.3": ["dreampop"], "20.6 5.0 12.8": ["crayola"], "11.6 3.6 -1.3": ["overpromoted"], "12.1 14.3 18.9": ["dracunculiasis"], "1.7 -0.8 1.5": ["punchlist"], "-8.1 -11.0 6.9": ["udom"], "7.6 4.8 4.7": ["andmanagement"], "14.9 16.7 9.8": ["bastardising"], "8.9 10.1 8.1": ["especiall"], "5.0 1.6 15.7": ["taas"], "-2.1 2.0 4.0": ["antimuscarinic"], "21.8 11.3 9.3": ["unloose"], "7.5 31.5 5.6": ["kulak"], "6.8 1.4 25.6": ["nickering"], "-8.4 10.2 2.9": ["empowerments"], "13.2 3.5 20.1": ["cordifolia"], "7.9 14.9 18.0": ["corne"], "19.0 8.9 11.1": ["slebs"], "13.0 1.5 19.7": ["borek"], "14.1 0.3 12.7": ["floragraph"], "12.7 12.2 16.9": ["robertson"], "-9.4 -4.8 3.5": ["bpts"], "-10.2 13.9 5.1": ["dilligence"], "11.3 -1.7 10.2": ["neurotech"], "-3.1 13.2 7.0": ["fomentation"], "2.2 -5.0 6.9": ["hybridomas"], "6.0 8.6 13.5": ["vogues"], "11.1 6.0 15.3": ["rollies"], "1.9 1.2 1.6": ["downregulates"], "8.0 12.0 14.5": ["becomingly"], "7.4 10.4 23.0": ["paisan"], "15.5 21.7 6.7": ["impedimenta"], "-0.4 12.3 8.5": ["synaptotagmin"], "6.3 -3.1 16.9": ["wholecrop"], "0.7 2.7 7.9": ["welldeserved"], "14.8 -0.4 16.3": ["chais"], "7.2 8.3 6.3": ["totalof"], "3.2 16.3 12.3": ["gratuitious"], "-1.3 11.6 14.2": ["aapki"], "-2.5 8.5 5.0": ["abus"], "5.2 7.9 5.5": ["negociate"], "30.8 9.5 5.7": ["chieftans"], "-3.5 -3.0 6.4": ["afs"], "3.3 6.1 21.7": ["myun"], "6.0 10.8 7.4": ["llegal"], "2.7 9.9 11.5": ["nanocubes"], "2.4 13.7 11.1": ["samay"], "10.5 3.4 12.1": ["rhapsodising"], "11.4 0.2 29.7": ["sternwheel"], "-1.8 -1.3 -0.5": ["atan"], "2.1 25.1 11.0": ["knowning"], "10.9 11.7 11.6": ["zoomer"], "13.4 11.9 12.3": ["unfulfillable"], "9.3 -2.7 2.9": ["kissogram"], "4.2 9.7 7.0": ["classificatory"], "-6.3 6.4 10.6": ["pupunta"], "1.0 15.6 11.0": ["obviosly"], "1.6 -2.1 5.7": ["tazobactam"], "2.2 7.1 5.1": ["recen"], "8.8 6.5 11.6": ["unceremonial"], "-3.1 3.5 4.6": ["scoing"], "-3.1 13.9 -2.1": ["antimetabolite"], "11.4 24.7 16.0": ["primordially"], "-4.2 23.9 5.6": ["frienship"], "8.7 -1.8 9.6": ["multigeneration"], "12.1 -1.1 17.9": ["burberry"], "12.3 9.5 7.0": ["plasmoids"], "21.1 9.1 20.1": ["waratah"], "8.9 1.7 11.8": ["micromini"], "-3.5 2.9 -1.8": ["dhc"], "14.3 17.2 21.5": ["liquidambar"], "1.3 -0.9 2.5": ["applicatio"], "0.2 3.9 1.9": ["serialist"], "0.2 15.5 4.3": ["translater"], "-7.9 4.1 0.7": ["theperformance"], "18.3 3.2 17.6": ["babygro"], "11.8 13.9 10.9": ["retrogrades"], "-0.2 15.0 6.8": ["hiw"], "-3.3 4.7 16.0": ["relasyon"], "4.3 37.0 4.4": ["brutalises"], "21.3 11.2 9.3": ["waggon"], "2.0 15.9 16.4": ["vetran"], "17.0 8.9 10.8": ["avertising"], "11.3 29.8 7.9": ["enkindle"], "8.4 5.4 30.5": ["primals"], "13.8 12.5 12.5": ["grabens"], "7.3 15.5 -1.3": ["tehran"], "4.2 16.9 16.9": ["hande"], "3.2 16.3 6.1": ["statis"], "5.4 0.2 16.3": ["bwe"], "16.5 0.9 5.5": ["alibaba"], "13.7 5.2 6.6": ["staduim"], "5.6 5.5 18.0": ["chortens"], "-1.5 10.4 13.0": ["hargreaves"], "1.8 -0.4 -4.6": ["tranparency"], "3.6 12.3 8.6": ["transcon"], "2.6 20.9 13.3": ["conformities"], "17.4 16.5 15.0": ["embiggen"], "7.4 9.6 13.1": ["backstick"], "17.1 22.7 11.4": ["dopplegangers"], "5.3 8.8 20.1": ["tippled"], "15.8 11.5 5.2": ["reemphasis"], "17.9 12.1 20.2": ["khada"], "16.3 2.9 31.5": ["epergne"], "10.7 11.6 14.1": ["southest"], "-2.0 4.2 2.9": ["esidents"], "-4.2 -2.9 1.5": ["expediture"], "13.1 6.7 13.7": ["nightglow"], "20.3 20.6 43.8": ["ruffe"], "1.3 10.6 14.0": ["butions"], "-7.0 2.7 1.9": ["adrenalectomy"], "13.0 8.8 11.2": ["reits"], "10.2 26.2 14.3": ["wishfulness"], "13.2 7.6 30.0": ["pakoda"], "7.3 27.5 -0.6": ["kalashnikov"], "3.7 2.3 14.5": ["nino"], "5.2 13.7 7.8": ["oculomotor"], "8.0 -11.3 9.3": ["througha"], "2.8 34.9 0.2": ["murtad"], "15.2 8.4 11.8": ["stucked"], "6.2 13.5 15.3": ["expectorations"], "-4.3 16.5 -2.2": ["reequipped"], "25.2 27.2 16.1": ["battleaxes"], "5.4 11.8 8.9": ["headcam"], "18.1 7.9 4.1": ["freerunners"], "8.7 13.6 10.8": ["boths"], "10.0 7.8 17.2": ["lunchbreaks"], "19.9 14.3 28.5": ["thorned"], "7.7 -1.7 6.5": ["patternmakers"], "4.2 20.2 10.0": ["perspicuous"], "-3.7 13.7 -0.5": ["ameen"], "17.4 18.4 13.2": ["omnibox"], "17.6 23.2 10.6": ["prostrates"], "6.4 8.6 9.9": ["xanthine"], "16.9 9.1 4.0": ["carsales"], "9.1 -7.9 7.5": ["nergy"], "13.8 2.4 20.1": ["arrastre"], "20.2 7.1 17.5": ["moke"], "5.6 22.1 16.5": ["arme"], "8.2 7.3 11.0": ["yardlines"], "2.9 0.5 10.4": ["ilobolo"], "7.5 10.3 -2.4": ["microquasar"], "16.3 6.0 10.7": ["repolished"], "6.7 -6.6 20.8": ["naples"], "7.5 8.8 -0.5": ["pyrometers"], "-2.1 9.4 3.7": ["efffort"], "8.7 10.5 11.1": ["barometre"], "12.6 4.0 15.6": ["gambolled"], "18.4 3.4 14.9": ["forexample"], "11.7 14.6 16.2": ["crowdsurfing"], "12.7 2.4 9.1": ["iphoto"], "7.2 -7.6 12.1": ["milyong"], "0.1 10.4 5.4": ["margain"], "8.7 8.2 11.0": ["bugzilla"], "10.1 13.6 14.8": ["hoor"], "-1.9 -2.6 1.6": ["orthotists"], "8.2 27.2 9.7": ["wrecklessly"], "4.6 7.7 14.9": ["permitees"], "9.2 5.7 5.1": ["jara"], "11.0 13.6 13.5": ["emocore"], "2.7 22.9 2.7": ["villification"], "6.1 14.4 13.8": ["crazypants"], "14.0 12.6 14.1": ["tighty"], "1.5 7.7 13.1": ["regalo"], "7.6 3.2 11.9": ["nzd"], "2.7 26.4 8.4": ["outchancing"], "2.9 4.3 11.4": ["hyperacidity"], "4.4 0.6 7.2": ["closeable"], "13.5 -1.4 4.4": ["cityof"], "1.0 10.6 3.1": ["unquotable"], "12.8 6.8 25.1": ["cullings"], "1.6 1.5 -0.3": ["prearranging"], "4.8 8.7 9.6": ["wwere"], "11.8 11.8 14.7": ["yappin"], "4.4 11.8 15.7": ["bestman"], "10.6 -4.6 -4.1": ["prelease"], "14.9 20.3 14.0": ["swineherd"], "11.4 13.6 27.7": ["melanistic"], "6.5 4.1 7.7": ["cryptorchid"], "7.3 -2.3 3.0": ["kabillion"], "-5.4 6.4 4.9": ["mamlatdars"], "2.3 7.5 8.3": ["aminopyralid"], "0.3 -6.2 -1.6": ["acsis"], "-0.8 9.0 1.9": ["deprival"], "-2.8 2.3 8.3": ["cce"], "8.5 20.7 5.7": ["oppponents"], "10.2 6.5 26.1": ["zatar"], "8.2 11.2 9.4": ["madd"], "11.7 11.8 11.7": ["replugging"], "15.7 11.3 12.1": ["webspam"], "1.4 3.8 2.7": ["thecall"], "0.2 2.3 5.2": ["secondes"], "15.5 1.6 9.2": ["mechano"], "20.5 -0.3 5.2": ["resurfacer"], "-6.8 16.8 12.0": ["cetain"], "2.6 7.2 15.5": ["hul"], "4.9 8.4 6.9": ["farmor"], "0.5 5.8 0.4": ["snippily"], "15.5 26.1 12.6": ["straightforwar"], "-5.1 -1.9 -3.3": ["espoirs"], "8.4 20.3 6.1": ["superordinate"], "18.4 8.6 33.5": ["pappadums"], "9.6 5.1 27.5": ["tsps"], "6.9 8.5 -5.6": ["interphone"], "6.7 -2.0 25.6": ["aravana"], "7.9 8.2 7.9": ["rohit"], "15.4 23.6 22.5": ["hrogers"], "4.2 5.1 4.7": ["dayton"], "10.0 12.8 12.9": ["volatilized"], "3.2 10.6 14.1": ["guessin"], "10.5 14.5 7.6": ["adulate"], "3.1 5.5 6.3": ["moja"], "18.8 11.3 5.8": ["superforce"], "8.1 1.5 12.4": ["flocculant"], "18.9 13.5 9.3": ["furores"], "5.6 12.3 10.2": ["quaterbacks"], "20.2 21.7 19.6": ["crawlin"], "-1.5 -1.6 8.7": ["rayons"], "-2.2 -5.0 7.9": ["pmol"], "10.0 8.9 6.5": ["clincal"], "12.8 5.5 18.3": ["barron"], "4.7 3.4 17.1": ["mastopexy"], "4.6 3.6 -4.9": ["itscustomers"], "17.5 28.8 14.1": ["riddler"], "-0.4 10.6 0.1": ["duplicable"], "18.8 4.3 12.7": ["keepy"], "6.3 17.8 0.8": ["offcer"], "13.3 16.0 19.4": ["wavefronts"], "15.0 9.6 6.9": ["kompa"], "2.7 10.9 7.8": ["omething"], "-5.7 20.2 9.8": ["overgeneralize"], "5.8 11.1 1.7": ["motormouths"], "0.9 5.4 10.2": ["curandero"], "-3.0 9.8 7.0": ["kaum"], "8.6 11.0 10.9": ["jollying"], "-3.4 20.0 8.6": ["subtribes"], "2.3 5.9 8.5": ["reexports"], "5.6 12.6 7.1": ["exoticized"], "12.7 12.8 27.4": ["scran"], "13.6 4.3 8.6": ["foodbowl"], "3.7 -2.4 12.3": ["osteology"], "6.1 -4.6 15.0": ["diversi"], "5.3 7.7 15.4": ["lakefronts"], "10.7 5.6 23.1": ["frio"], "7.9 6.3 3.5": ["nonaviation"], "5.7 1.8 15.2": ["microvias"], "4.5 15.3 15.5": ["pease"], "3.2 2.8 -7.2": ["usiness"], "-0.7 18.1 1.2": ["oppinions"], "12.5 10.1 35.0": ["pignoli"], "0.0 3.4 6.1": ["halli"], "15.5 6.3 18.3": ["jumpsuited"], "10.4 -4.0 4.9": ["rasie"], "-6.5 4.3 2.8": ["sucessfull"], "4.5 -4.7 4.4": ["precription"], "6.7 -5.2 2.0": ["mpact"], "4.1 23.0 0.8": ["nonobservant"], "8.5 23.4 9.2": ["pararescuers"], "17.4 4.2 11.1": ["ederal"], "15.3 1.1 4.7": ["behnd"], "18.4 1.4 12.3": ["exch"], "8.9 6.7 10.3": ["eak"], "-3.9 -3.0 15.2": ["hhs"], "13.4 8.3 21.0": ["relandscaping"], "20.5 21.0 31.6": ["luggers"], "6.9 -0.5 5.4": ["milch"], "0.6 6.7 7.4": ["richtig"], "10.1 1.2 10.7": ["apertura"], "12.0 4.6 7.2": ["farmee"], "-8.5 3.6 3.3": ["capiases"], "10.1 18.5 16.2": ["lawd"], "20.0 9.9 19.6": ["cirques"], "5.7 28.9 9.8": ["biotics"], "9.7 3.6 12.2": ["postview"], "23.2 18.8 23.8": ["frontloader"], "2.9 6.1 -3.1": ["earch"], "2.1 1.3 6.5": ["washpost"], "15.8 11.1 7.2": ["cheaped"], "21.2 7.7 17.3": ["plectrums"], "2.3 -4.7 22.0": ["debra"], "0.4 7.3 3.9": ["dismisal"], "2.8 8.6 3.6": ["futureperformance"], "12.5 13.7 13.4": ["agoraphobe"], "-1.4 2.5 10.6": ["casher"], "9.1 15.2 18.9": ["footstones"], "3.9 -2.6 -8.7": ["commonground"], "18.7 12.5 20.2": ["bunnet"], "21.6 10.8 27.8": ["parasails"], "2.1 40.0 9.1": ["artillary"], "-0.3 -6.8 23.6": ["matchings"], "8.9 16.2 14.5": ["sillyness"], "6.2 9.9 17.1": ["alternaria"], "10.3 3.2 10.1": ["orimulsion"], "-3.6 3.2 10.8": ["boomerangers"], "4.6 -6.7 -3.6": ["sameday"], "17.8 2.5 6.6": ["familyowned"], "7.6 14.8 16.8": ["queerer"], "-0.4 14.8 12.2": ["intactness"], "15.4 23.0 10.0": ["caltrops"], "6.9 3.7 9.7": ["pilus"], "-0.2 8.6 15.3": ["gobernador"], "8.0 20.8 15.7": ["inclemency"], "6.1 -2.9 8.6": ["photocard"], "14.5 21.3 3.6": ["tehir"], "4.6 17.0 12.7": ["miscontrols"], "14.6 1.0 7.0": ["fastman"], "6.8 2.6 1.8": ["verage"], "-0.5 -4.8 -0.3": ["eague"], "-0.1 3.8 2.0": ["efonica"], "10.9 9.7 15.0": ["nudies"], "-1.1 -4.0 11.1": ["bodyworker"], "15.2 -5.1 6.7": ["abrubtly"], "4.7 8.6 13.7": ["karigars"], "2.4 21.1 1.3": ["vindications"], "-1.1 4.6 11.9": ["proff"], "10.8 21.7 -0.3": ["refusniks"], "5.9 21.4 7.9": ["allegoric"], "5.5 31.3 8.7": ["refought"], "4.9 5.2 -1.8": ["cartelists"], "0.8 1.7 10.1": ["forman"], "5.2 39.9 2.7": ["miliants"], "15.4 -0.0 19.8": ["quickservice"], "12.9 18.3 5.6": ["thunderingly"], "31.1 8.4 13.9": ["videoscreen"], "-2.8 4.9 -3.8": ["availale"], "13.5 6.6 19.6": ["tamboura"], "21.0 -0.3 11.6": ["multiblock"], "-8.3 9.5 3.8": ["asis"], "9.4 18.6 5.8": ["xaitment"], "5.2 4.0 8.6": ["untilthe"], "7.3 17.6 15.4": ["shadowland"], "3.1 1.0 1.7": ["sigining"], "-2.4 3.6 8.8": ["calo"], "3.7 11.2 20.3": ["veraison"], "-2.4 9.4 10.4": ["nickleback"], "4.7 -0.5 19.8": ["greisen"], "5.9 -4.2 2.9": ["sicknotes"], "18.8 4.6 20.0": ["sunporch"], "2.2 8.0 15.2": ["centrioles"], "8.5 12.6 7.6": ["glucuronolactone"], "3.8 -8.6 0.1": ["postcollegiate"], "9.4 2.8 16.5": ["dewey"], "15.0 3.9 14.0": ["underlayments"], "-8.4 12.8 3.5": ["constitional"], "2.7 0.7 11.5": ["nontransportation"], "6.2 5.5 6.7": ["fandangos"], "1.6 4.6 -3.7": ["natonal"], "6.2 2.5 13.1": ["unfused"], "7.0 14.3 9.5": ["polynucleotides"], "-0.4 12.0 2.5": ["haave"], "13.2 2.9 0.8": ["onco"], "10.8 -4.2 13.2": ["markes"], "18.6 12.3 11.6": ["motorscooters"], "10.0 22.0 18.3": ["highwater"], "2.0 18.3 4.3": ["readiest"], "11.5 19.5 11.0": ["sleeplessly"], "15.0 6.5 14.0": ["visably"], "-5.1 9.1 5.9": ["solubilize"], "-5.3 -14.4 3.3": ["dth"], "5.1 -1.0 4.8": ["facil"], "15.7 12.1 9.5": ["quintillions"], "8.8 20.1 15.6": ["headkick"], "8.5 5.7 8.1": ["deemphasizes"], "5.7 11.8 6.1": ["nonwestern"], "17.9 18.2 19.7": ["northlands"], "5.9 0.7 16.9": ["haga"], "7.9 5.3 11.3": ["conrods"], "8.1 4.4 15.4": ["nanosprings"], "6.8 16.1 2.0": ["suppoters"], "12.7 12.3 26.8": ["domesticus"], "5.6 0.9 18.1": ["sucklers"], "13.0 9.7 4.5": ["acomplete"], "1.5 15.7 17.7": ["diha"], "-7.1 -5.8 0.2": ["subgrantees"], "18.4 12.0 2.9": ["orgone"], "26.1 8.1 5.0": ["swooshy"], "12.3 -3.8 1.3": ["matrimonials"], "8.9 -4.9 4.9": ["tomore"], "5.5 8.6 11.1": ["clusterflock"], "8.5 16.4 15.1": ["raygu"], "17.8 17.4 -0.5": ["alchemize"], "-7.8 1.1 1.6": ["ineligble"], "6.3 10.8 9.0": ["antitumour"], "11.2 16.6 11.6": ["lambo"], "14.6 11.4 21.5": ["merle"], "4.9 12.6 9.2": ["tuples"], "10.3 18.6 19.1": ["bodyscissors"], "9.0 16.1 10.0": ["kadam"], "1.3 -4.3 18.4": ["frais"], "5.3 8.7 3.6": ["xenobiotic"], "6.1 -4.1 -1.9": ["inet"], "7.3 -0.4 9.2": ["ecord"], "2.8 2.8 21.8": ["brunchers"], "-7.2 -3.6 2.5": ["registar"], "-2.0 22.2 11.0": ["berachah"], "11.3 4.9 4.0": ["psychophysics"], "5.9 12.9 7.5": ["underseepage"], "5.8 11.5 7.9": ["pappi"], "28.0 23.8 12.7": ["toytown"], "1.9 2.3 11.9": ["wohi"], "18.6 7.0 20.4": ["coalman"], "2.9 10.7 6.6": ["sentances"], "15.2 6.7 17.9": ["poptart"], "-4.0 -7.3 6.4": ["kih"], "8.0 0.8 5.1": ["bustup"], "17.6 -1.0 24.3": ["dentil"], "15.6 18.3 9.2": ["klansman"], "12.4 -5.4 -0.5": ["poular"], "3.8 2.2 10.4": ["rigless"], "12.3 -3.5 -0.5": ["informitv"], "1.7 11.6 21.3": ["chira"], "-2.1 5.3 8.7": ["solvation"], "17.3 0.8 -3.0": ["tronics"], "12.6 4.3 12.9": ["panelbeaters"], "10.2 -8.1 -6.4": ["cofound"], "10.2 16.0 8.8": ["directon"], "7.5 16.4 11.1": ["whiteboy"], "9.3 2.9 5.6": ["ddn"], "5.4 3.7 17.1": ["overfills"], "5.7 6.8 8.3": ["spallation"], "5.3 5.8 24.3": ["shao"], "5.8 2.3 -4.3": ["alledge"], "9.8 -6.4 1.1": ["zenon"], "7.5 24.4 8.7": ["handmaids"], "6.2 8.0 12.4": ["cuppings"], "2.2 16.5 10.6": ["probobly"], "17.7 2.9 10.1": ["tablers"], "8.4 5.8 5.4": ["diz"], "11.7 7.4 5.5": ["weill"], "6.3 19.6 16.5": ["monolingualism"], "6.8 2.6 2.3": ["ormore"], "7.1 9.0 18.4": ["enargite"], "8.5 7.0 -1.2": ["nasheed"], "12.6 6.5 17.7": ["nikkei"], "1.4 17.5 9.2": ["creational"], "-3.3 4.4 4.3": ["toall"], "16.2 15.1 8.7": ["outdating"], "13.2 6.5 4.9": ["aunique"], "4.5 -0.1 9.0": ["gymastics"], "3.9 16.2 8.6": ["adaptogens"], "-4.7 1.2 -2.7": ["nomine"], "10.2 4.5 23.5": ["safrole"], "1.2 8.1 18.5": ["proseso"], "7.3 7.3 8.0": ["nannygate"], "6.8 7.6 9.6": ["trialler"], "5.8 -0.7 3.2": ["concall"], "-0.6 23.8 8.3": ["humanbeing"], "-6.2 17.4 3.1": ["anhu"], "8.1 25.6 5.1": ["refortify"], "10.2 2.7 27.3": ["cooke"], "9.4 2.9 21.2": ["fossick"], "3.7 15.1 3.9": ["knowlegeable"], "10.4 10.4 13.8": ["nosegear"], "7.6 13.9 11.0": ["chilla"], "4.6 -0.2 7.9": ["imrpove"], "7.2 10.2 3.4": ["alround"], "3.5 0.1 9.9": ["halfmile"], "5.5 1.5 15.1": ["durham"], "-2.3 8.2 2.3": ["antiarrhythmics"], "9.9 13.4 21.3": ["coccinea"], "1.9 7.1 17.0": ["nizzle"], "-4.9 5.9 4.3": ["ampton"], "7.9 2.2 4.1": ["mcel"], "3.9 9.4 12.4": ["jyoti"], "0.2 13.6 11.6": ["nini"], "7.8 10.1 16.1": ["cristina"], "2.9 7.9 17.4": ["grabe"], "22.0 10.5 24.6": ["oinkers"], "20.5 -2.4 3.7": ["houser"], "8.2 6.2 9.9": ["retin"], "0.4 12.6 5.9": ["apperceive"], "15.9 -2.9 16.9": ["pipestone"], "8.2 2.9 19.4": ["plowable"], "16.3 16.1 13.6": ["nonreflective"], "1.1 8.8 5.2": ["unser"], "5.5 8.4 15.6": ["lifties"], "-2.9 -4.0 7.0": ["opcode"], "28.5 2.6 12.1": ["podlike"], "0.1 17.1 9.6": ["eally"], "6.7 17.8 11.9": ["preppers"], "8.5 14.8 16.4": ["whammed"], "-1.2 7.8 39.8": ["redfishing"], "-0.3 -3.0 1.5": ["repetiteur"], "3.9 4.0 13.1": ["orcharding"], "16.3 5.9 22.0": ["microbialites"], "8.0 -0.9 7.4": ["mixeduse"], "-0.5 10.6 6.9": ["bandgaps"], "14.8 6.5 5.8": ["lorryloads"], "2.5 19.2 12.1": ["waymark"], "18.3 9.1 16.4": ["likea"], "13.8 6.1 1.4": ["trasher"], "7.7 4.2 0.1": ["hydrocrackers"], "14.5 16.3 41.4": ["whiskerfish"], "10.2 5.1 9.0": ["unformulated"], "10.1 29.0 10.6": ["remorselessness"], "4.3 7.6 15.5": ["mahu"], "8.5 11.7 11.4": ["roshan"], "23.5 14.7 17.5": ["franken"], "25.6 30.8 13.3": ["repulsor"], "12.1 10.3 13.8": ["strongish"], "15.8 7.7 19.0": ["acers"], "26.6 21.1 22.3": ["squirty"], "6.1 25.9 12.9": ["viziers"], "17.1 11.5 13.1": ["fumigator"], "8.5 -6.2 3.9": ["collators"], "9.9 26.4 7.0": ["demarked"], "-4.7 8.6 8.1": ["loks"], "1.0 16.3 7.4": ["mukti"], "1.1 5.6 21.8": ["lemma"], "15.3 13.6 12.8": ["trues"], "-8.6 5.4 4.0": ["andall"], "14.8 0.7 6.2": ["invididuals"], "-1.6 6.4 17.5": ["suff"], "-2.7 6.7 0.8": ["captioner"], "3.9 5.8 10.6": ["vivace"], "10.7 14.1 7.3": ["locknut"], "4.2 11.0 15.9": ["retroceded"], "16.3 15.8 12.3": ["unsprung"], "5.3 28.9 9.2": ["ineffectualness"], "-0.5 11.6 10.9": ["multichassis"], "9.2 1.0 15.0": ["whiskys"], "9.2 15.8 2.7": ["slaught"], "15.4 7.1 5.7": ["awashed"], "3.5 -5.9 5.2": ["ideablob"], "-0.4 14.7 8.5": ["becauses"], "-0.6 2.9 19.2": ["definitives"], "-3.2 8.5 6.3": ["journaliste"], "14.4 10.8 12.7": ["hilarous"], "-3.0 -3.3 3.3": ["arthroplasties"], "-6.4 -7.1 5.4": ["douzaine"], "4.1 9.7 0.1": ["poststructuralist"], "4.7 5.6 -2.4": ["conductorless"], "13.3 18.3 0.2": ["builidng"], "21.3 12.1 29.7": ["pulk"], "13.8 3.7 1.2": ["datawarehousing"], "20.0 2.9 9.8": ["nailhead"], "2.8 -0.9 15.7": ["nant"], "2.4 0.2 -0.4": ["signes"], "10.3 8.8 5.3": ["littany"], "24.8 17.5 39.3": ["redtail"], "2.8 5.7 14.1": ["hammermill"], "0.4 12.1 10.3": ["ventromedial"], "18.6 8.7 7.8": ["helio"], "9.5 10.3 4.4": ["unclick"], "7.2 7.1 -4.2": ["establishe"], "11.5 8.0 31.4": ["ribollita"], "-3.6 5.1 10.3": ["seconddegree"], "3.0 2.2 7.2": ["teleseries"], "2.6 5.2 3.7": ["dihydroergotamine"], "2.7 8.5 10.6": ["coalescent"], "9.2 4.7 16.9": ["strada"], "10.5 2.8 10.7": ["vinotherapy"], "-1.1 8.6 12.6": ["humne"], "-6.7 21.2 -1.2": ["incarcerator"], "22.3 11.7 21.8": ["inglenook"], "3.8 9.1 9.4": ["selfsufficient"], "3.4 6.9 8.4": ["unrespectable"], "4.4 -1.3 5.1": ["chansonnier"], "0.2 19.0 14.0": ["nonresistant"], "11.6 11.9 3.2": ["keke"], "1.3 10.1 6.5": ["brainstormers"], "-3.3 1.6 17.1": ["lette"], "12.7 18.1 0.8": ["possbility"], "11.2 6.4 -8.2": ["teleprompting"], "12.7 8.2 -0.7": ["redomiciling"], "3.1 3.9 1.7": ["subcircuits"], "4.3 5.7 14.5": ["batho"], "15.9 13.4 20.9": ["wreathe"], "5.9 7.0 -4.9": ["conject"], "17.5 0.7 -0.1": ["fromits"], "18.0 12.0 25.2": ["choanoflagellates"], "-3.6 3.3 9.3": ["nonpriority"], "4.8 -3.8 9.5": ["precertified"], "0.8 9.4 3.7": ["fieldgoals"], "6.9 -2.4 16.6": ["sheanuts"], "-3.9 5.6 4.3": ["aamir"], "-5.2 41.3 4.7": ["reconcilables"], "7.4 -1.9 6.1": ["onair"], "-2.4 15.6 16.0": ["orderings"], "12.1 8.8 13.6": ["curiousindependent"], "1.0 7.8 4.2": ["experinced"], "3.6 10.8 2.6": ["sieht"], "1.1 20.5 2.0": ["sacralized"], "7.6 11.2 19.1": ["ramidus"], "7.8 0.5 2.5": ["electri"], "5.9 15.2 7.0": ["iot"], "1.2 10.4 12.1": ["cassie"], "5.2 1.1 10.7": ["cervices"], "-3.0 10.1 2.5": ["releiver"], "0.6 0.3 6.9": ["treas"], "8.0 6.8 15.2": ["brennan"], "6.2 12.0 14.9": ["augue"], "2.0 30.3 2.4": ["basijis"], "-9.5 5.3 4.8": ["aetiological"], "-3.2 15.8 -1.8": ["sensus"], "12.8 2.5 3.4": ["isses"], "2.9 8.7 14.1": ["muggier"], "12.6 1.8 15.8": ["thinkproducts"], "16.3 16.8 12.5": ["shitless"], "-0.7 6.2 3.1": ["complexation"], "10.4 12.5 10.1": ["rewinders"], "0.7 5.7 7.2": ["trichloroethane"], "5.1 17.7 21.0": ["evolvability"], "5.8 8.1 2.6": ["isno"], "-1.3 0.4 -1.7": ["submeter"], "2.6 3.6 6.4": ["unindexed", "bisulfate"], "-0.8 4.4 16.8": ["tulungan"], "10.0 14.1 5.2": ["fourway"], "19.2 7.5 4.4": ["ultrastrong"], "1.6 19.0 4.3": ["predicition"], "4.8 28.5 6.2": ["outlander"], "2.1 10.6 29.3": ["phirni"], "15.7 -1.6 7.2": ["impoved"], "6.2 22.8 11.9": ["popularism"], "4.4 11.9 11.6": ["upseting"], "14.1 1.6 4.0": ["motorplex"], "-0.8 10.9 5.9": ["morafe"], "25.0 2.7 26.1": ["cachepot"], "6.4 12.4 5.6": ["sarabande"], "4.6 11.4 3.7": ["unconventionals"], "3.3 17.0 3.3": ["interuptions"], "17.8 18.2 8.1": ["ganger"], "-3.0 17.7 3.5": ["multipartism"], "9.7 7.0 11.9": ["doot"], "4.5 8.3 5.1": ["nvestigators"], "13.8 23.1 9.8": ["agrarianism"], "9.9 23.2 11.6": ["unavailingly"], "13.5 10.9 13.0": ["hobbiest"], "10.5 12.9 5.1": ["mouseclick"], "25.8 18.4 34.7": ["remoras"], "9.0 5.1 9.9": ["afour"], "-12.2 1.0 -4.8": ["secreatry"], "21.5 6.2 15.1": ["storer"], "-0.5 1.7 7.8": ["poppermost"], "3.7 28.0 6.0": ["propagandizes"], "9.3 9.3 24.8": ["thom"], "3.9 3.8 7.5": ["allimportant"], "5.3 3.0 2.7": ["athetes"], "10.1 0.9 7.2": ["lengendary"], "4.9 18.0 12.6": ["believin"], "10.1 16.8 11.9": ["decrescendos"], "9.0 7.2 44.9": ["elver"], "10.3 10.9 24.1": ["enjoyin"], "1.6 22.4 11.8": ["empathies"], "6.8 2.1 20.5": ["wf"], "5.2 -0.7 15.1": ["goot"], "11.2 5.4 13.9": ["tremblingly"], "4.4 5.9 11.0": ["babyboomer"], "3.9 10.9 17.9": ["overpacking"], "6.9 6.6 11.4": ["bedfast"], "7.2 13.8 20.4": ["unk"], "-5.4 3.8 8.0": ["cowriters"], "11.9 16.6 11.6": ["slashdotters"], "8.5 6.1 15.5": ["mochila"], "11.9 11.8 16.3": ["caesars"], "-4.2 3.4 -0.7": ["illumio"], "4.1 6.0 6.0": ["scutiny"], "13.3 14.8 -5.4": ["resurgency"], "12.0 22.3 9.3": ["nakeds"], "6.5 22.1 6.8": ["sockpuppet"], "-4.4 7.5 5.7": ["kagawads"], "5.2 18.9 11.9": ["spellcheckers"], "2.6 10.1 0.7": ["waaaaaaaay"], "4.1 27.5 6.6": ["hatered"], "9.1 4.9 8.6": ["strippable"], "5.1 6.8 -1.8": ["exasperations"], "4.8 -1.7 15.1": ["relo"], "6.2 -1.2 -1.6": ["untap"], "13.0 14.3 22.9": ["needin"], "2.1 12.8 10.0": ["wais"], "6.7 17.3 12.4": ["biocontrols"], "18.8 4.1 10.1": ["styl"], "7.9 9.0 3.9": ["inholding"], "17.3 10.5 -4.5": ["thebuilding"], "0.3 6.6 -0.1": ["decentered"], "13.1 16.2 15.5": ["pantomimic"], "8.8 9.3 22.5": ["boatless"], "-3.1 -0.8 -1.8": ["novosti"], "6.9 4.9 6.2": ["feddan"], "4.2 27.9 6.7": ["tribalized"], "8.2 7.4 11.3": ["sahre"], "7.1 4.2 17.2": ["nonanimal"], "-1.3 4.2 9.6": ["reweight"], "1.6 13.7 0.9": ["groundlessness"], "11.6 -3.9 0.8": ["celebrat"], "2.7 10.8 11.0": ["distensibility"], "0.3 8.5 7.9": ["uninitialized"], "-2.7 4.1 10.0": ["nonvested"], "5.1 -0.5 10.0": ["followi"], "8.3 25.5 3.7": ["beleif"], "6.4 20.6 10.4": ["gubbed"], "13.3 17.5 3.8": ["blacklash"], "4.0 22.7 9.1": ["sperate"], "11.2 5.2 -1.5": ["patnership"], "8.2 12.8 18.7": ["beefin"], "-1.8 4.1 3.1": ["hdnetfights"], "16.3 17.8 40.6": ["jaegers"], "-4.4 -1.6 7.8": ["etodolac"], "14.4 6.8 19.5": ["pasteurise"], "2.0 10.9 13.6": ["assman"], "14.9 10.5 20.5": ["florin"], "-8.8 0.2 0.3": ["amed"], "-2.6 18.7 13.1": ["alienations"], "12.0 16.2 21.1": ["biomagnification"], "13.2 7.8 -0.7": ["venezuelan"], "-5.5 7.9 10.5": ["nonhighway"], "10.9 3.2 7.4": ["internacionales"], "3.3 8.5 -3.4": ["negotions"], "1.6 5.9 2.4": ["multifunctions"], "9.6 14.0 6.1": ["ghettoising"], "12.9 6.6 4.8": ["eported"], "-4.8 -4.1 -6.5": ["enroller"], "-1.3 15.7 9.4": ["pathologized"], "-5.3 1.8 3.1": ["haematuria"], "1.3 10.8 8.7": ["chartable"], "4.8 12.0 18.6": ["buon"], "9.0 -4.4 33.8": ["pirohi"], "8.3 22.0 7.3": ["georgian"], "3.8 21.3 11.1": ["triterpenoids"], "6.8 5.9 10.4": ["clamav"], "-4.6 16.5 5.6": ["thereunto"], "3.9 -9.7 7.4": ["nuhr"], "-2.0 -0.5 10.3": ["flugelhornist"], "-2.6 -0.9 15.5": ["kidu"], "10.4 34.3 1.9": ["rearms"], "7.6 6.5 23.0": ["ciborium"], "2.0 12.9 10.0": ["imigrants"], "14.9 11.9 27.5": ["mingy"], "11.1 5.7 10.0": ["deleverages"], "14.1 13.7 6.0": ["onyour"], "12.3 18.7 22.5": ["ulcerate"], "5.4 13.0 16.6": ["deary"], "1.6 -1.5 -10.2": ["initiave"], "23.9 5.4 20.6": ["rockwall"], "16.0 15.6 4.8": ["pixar"], "5.4 22.5 7.9": ["bewitchment"], "24.9 10.2 24.4": ["pitter"], "7.7 21.3 18.5": ["killable"], "12.4 10.9 24.6": ["tragus"], "17.7 12.4 11.9": ["smarpthone"], "-2.0 -4.0 -7.3": ["previosly"], "18.7 12.1 17.8": ["botty"], "3.8 11.6 18.2": ["williamson"], "-0.1 20.3 9.3": ["nasri"], "9.9 5.5 23.2": ["recloseable"], "9.7 0.8 14.5": ["woollier"], "-8.5 14.6 6.3": ["committeeperson"], "3.5 16.3 6.7": ["providences"], "5.0 10.8 17.3": ["kilig"], "4.6 6.5 15.3": ["subchondral"], "2.1 14.2 9.2": ["misdemeanant"], "4.1 -0.6 7.1": ["swatchbook"], "2.3 2.7 4.1": ["polytherapy"], "7.6 13.1 -1.6": ["talkless"], "2.9 25.8 -0.2": ["unjustice"], "2.0 3.5 3.3": ["tantri"], "6.4 21.2 16.5": ["ungainliness"], "12.6 18.9 11.4": ["muckrake"], "9.3 5.7 10.2": ["sialidase"], "3.8 5.9 14.0": ["viaje"], "6.1 1.4 29.7": ["dook"], "6.7 2.8 25.6": ["affinis"], "11.1 4.9 16.2": ["quarryman"], "7.9 12.0 0.7": ["refreshable"], "4.2 17.6 6.4": ["prating"], "-3.8 12.1 -1.3": ["firman"], "12.7 11.3 22.2": ["sauropodomorphs"], "14.5 19.1 9.6": ["grayware"], "8.9 29.4 11.9": ["tyranical"], "7.2 7.2 7.5": ["proferring"], "3.3 7.1 6.7": ["impactof"], "21.0 6.4 13.1": ["diagrid"], "3.2 -3.6 -7.0": ["inaugrated"], "1.8 -0.5 5.4": ["aho"], "6.4 26.0 14.3": ["ethnonationalism"], "17.2 12.2 11.9": ["sandblasters"], "13.5 19.6 6.9": ["cyclosarin"], "-7.3 23.6 10.9": ["oxfordspur"], "0.7 12.4 7.4": ["shouldas"], "3.3 11.6 15.1": ["memset"], "2.8 6.7 5.4": ["norfloxacin"], "3.0 5.1 25.7": ["riverkeepers"], "3.4 16.1 19.8": ["itand"], "4.2 7.8 5.6": ["convoluting", "chordae"], "19.9 16.9 13.2": ["bellyachers"], "14.8 4.7 17.5": ["coiler"], "0.9 2.5 1.5": ["venules"], "36.4 6.8 9.9": ["squillionaire"], "17.3 5.2 25.2": ["baccy"], "5.7 15.6 0.4": ["motiviation"], "6.3 -0.6 9.1": ["wangles"], "4.3 14.2 15.0": ["peyton"], "0.9 5.7 2.6": ["besoin"], "5.2 2.0 5.5": ["brainstems"], "4.4 15.6 11.5": ["inhabitance"], "15.0 7.1 5.8": ["restucturing"], "7.4 -2.8 12.6": ["profittaking"], "7.0 -1.6 9.3": ["degumming"], "3.4 6.7 6.9": ["slickwater"], "16.0 36.0 11.4": ["griefer"], "-1.6 5.1 11.3": ["cyrus"], "11.4 -2.1 31.5": ["champignons"], "14.8 20.8 6.3": ["cybersphere"], "9.8 12.3 14.6": ["folie"], "8.0 4.5 1.0": ["tubthump"], "5.4 11.3 3.0": ["resync"], "0.5 -1.1 -2.8": ["anteromedial"], "10.0 24.4 8.7": ["sensitivies"], "-5.4 13.5 10.0": ["neuroinflammatory"], "3.0 9.5 14.0": ["chromatids"], "11.7 1.4 28.2": ["koeksisters"], "2.1 -1.1 7.0": ["phosphocreatine"], "13.5 0.2 7.0": ["businss"], "7.8 4.6 15.8": ["rsh"], "4.0 4.7 19.2": ["anh"], "9.5 3.8 17.2": ["microbrewed"], "0.6 -3.0 4.8": ["nonprimary"], "6.9 17.7 3.9": ["renascence"], "6.2 -6.0 1.7": ["partenaires"], "-3.4 6.5 6.7": ["antiestrogens"], "2.4 1.2 9.6": ["intradistrict"], "11.8 6.0 8.8": ["unitisation"], "6.0 5.6 12.8": ["sakadas"], "14.5 9.9 10.5": ["substanceless"], "7.6 11.9 -1.1": ["disfavours"], "9.9 17.6 9.5": ["sentimentalise"], "-2.5 4.5 7.6": ["dementing"], "24.6 3.6 13.8": ["nicknacks"], "5.5 28.9 11.6": ["exclusionism"], "6.5 8.9 2.2": ["infantilisation"], "14.6 28.4 8.3": ["vivisectors"], "18.5 6.8 3.5": ["contruct"], "3.6 0.7 11.6": ["viagara"], "30.3 2.0 28.5": ["maypoles"], "17.4 22.7 30.4": ["biotope"], "1.6 12.4 14.5": ["hophead"], "3.0 -1.4 4.3": ["outdanced"], "10.6 5.8 13.1": ["rhombic"], "16.2 6.3 28.3": ["sammie"], "12.1 1.6 10.7": ["diacylglycerol"], "10.0 6.1 18.0": ["foss"], "4.1 8.9 -3.8": ["broacast"], "6.7 26.3 6.8": ["foolhardily"], "-10.0 6.1 -1.3": ["expained"], "11.6 2.1 -0.0": ["euronewspure"], "14.4 7.6 26.4": ["oeuf"], "13.6 24.8 3.7": ["nighmare"], "2.5 2.8 12.8": ["cun"], "-5.8 13.2 1.6": ["pipo"], "7.3 18.5 11.0": ["harborer"], "3.9 21.7 -6.8": ["islamophobic"], "-1.5 10.1 0.4": ["renumerated"], "6.5 13.3 13.2": ["interwined"], "10.2 14.3 14.9": ["surrealness"], "14.9 5.1 -2.7": ["netcom"], "7.5 -0.4 -1.0": ["entavio"], "12.9 5.9 27.3": ["soundside"], "7.1 29.6 11.9": ["womanpower"], "9.1 5.0 13.9": ["gritstone"], "5.3 2.1 12.3": ["bhal"], "8.8 2.8 5.8": ["contemporise"], "9.8 1.8 12.5": ["pantone"], "4.9 -1.6 9.9": ["gavelled"], "13.4 19.7 13.2": ["brassiest"], "13.1 12.6 4.6": ["toclose"], "14.0 5.2 27.7": ["bluegum"], "4.8 5.0 19.4": ["recycleables"], "2.7 24.4 -0.4": ["counternarrative"], "8.1 1.1 12.6": ["incluso"], "0.6 7.4 15.5": ["bayad"], "4.4 4.3 8.1": ["mannat"], "2.2 7.5 10.5": ["rhymin"], "22.8 14.7 23.0": ["hokeypokey"], "-0.3 -0.2 14.8": ["tering"], "10.7 24.4 4.2": ["tripoli"], "6.4 7.5 10.0": ["seires"], "8.2 16.0 22.5": ["cakier"], "2.0 13.6 3.6": ["upfitter"], "9.0 8.8 4.0": ["closley"], "2.4 1.9 6.2": ["nervier"], "5.0 -2.5 10.5": ["arbennig"], "9.3 20.6 14.6": ["solice"], "-3.6 2.9 7.9": ["thaler"], "5.8 16.1 2.0": ["anticonstitutional"], "10.0 -1.5 17.4": ["artware"], "2.4 1.2 8.5": ["debat"], "6.1 29.6 2.1": ["weaponising"], "15.2 7.6 1.8": ["insitutional"], "8.4 -1.6 5.4": ["shrd"], "3.4 18.8 0.7": ["discribe"], "15.0 19.3 15.4": ["buncombe"], "1.2 -4.5 2.2": ["internationaux"], "7.3 -1.1 16.1": ["psytrance"], "-1.0 11.9 9.0": ["pinchhitter"], "0.6 -1.4 5.5": ["genu"], "-5.4 4.3 -7.9": ["ghanaweb"], "-4.0 7.0 9.2": ["contributable", "cinegoer"], "13.0 10.9 14.3": ["mest"], "0.9 5.7 23.5": ["metapopulation"], "6.7 1.3 0.3": ["omes"], "19.0 16.3 20.6": ["whimpy"], "9.3 10.8 5.8": ["reconsecrated"], "-3.2 0.2 -2.2": ["prolyl"], "21.1 16.1 11.6": ["monopine"], "-5.6 -3.9 -1.8": ["enquries"], "2.5 10.8 -2.7": ["nist"], "6.6 5.1 -0.6": ["eschewal"], "19.2 1.6 25.0": ["parmo"], "9.6 17.1 19.5": ["bodypress"], "0.9 -9.2 3.0": ["reimplemented"], "26.2 14.5 21.4": ["breadknife"], "6.2 8.6 10.6": ["turpis"], "11.3 6.0 15.2": ["cheval"], "0.2 7.7 24.6": ["wolfdogs"], "8.7 11.5 21.9": ["pinworm"], "4.2 -2.3 15.0": ["finshes"], "4.1 16.3 8.5": ["retrograded"], "14.0 14.0 24.6": ["wavery"], "14.3 27.5 15.2": ["spellbook"], "3.5 -3.3 4.9": ["subtransmission"], "11.0 5.6 11.1": ["preplaced"], "17.2 14.3 20.2": ["yukky"], "-2.3 2.2 -2.5": ["preisdent"], "11.9 15.0 13.0": ["neglectfully"], "2.2 1.4 19.5": ["jollification"], "11.5 2.5 15.5": ["midranges"], "11.4 14.3 5.3": ["unchaining"], "11.5 13.4 6.2": ["yawnfest"], "0.7 6.9 0.2": ["torezolid"], "2.0 5.3 8.6": ["brid"], "14.9 18.3 27.7": ["tapetails"], "0.3 6.9 12.9": ["juliana"], "13.4 16.7 18.0": ["mudlarks"], "9.0 23.8 25.3": ["witchweed"], "5.2 -5.0 -7.8": ["libaries"], "9.6 15.5 1.6": ["blockings"], "-3.7 -4.4 14.8": ["dering"], "15.5 7.9 5.5": ["cyberdissident"], "12.1 2.5 3.4": ["chargeless"], "10.1 4.8 12.6": ["sela"], "11.3 12.3 14.8": ["prewriting"], "4.0 6.7 1.4": ["contemporised"], "2.0 8.0 7.7": ["seised"], "16.3 6.2 0.9": ["podia"], "9.7 9.5 8.2": ["prebuttal"], "12.1 9.8 6.9": ["spareparts"], "8.1 10.3 18.5": ["hamsa"], "9.5 2.5 3.7": ["propsals"], "0.3 15.5 6.6": ["dephasing"], "9.1 9.6 10.1": ["bowen"], "8.8 4.1 12.4": ["lita"], "0.3 10.8 0.9": ["megasonic"], "6.6 7.2 8.8": ["stds"], "11.2 0.6 11.7": ["powerheads"], "3.2 7.8 2.7": ["extensometer"], "13.8 15.4 8.1": ["graffitist"], "1.3 7.5 9.7": ["fortunefx"], "5.5 7.6 5.4": ["decible"], "10.1 -2.4 15.9": ["ginghams"], "15.7 14.7 12.1": ["onand"], "15.5 5.1 18.0": ["artemesia"], "12.7 2.2 6.4": ["alocal"], "10.0 7.2 4.4": ["illegalization"], "17.1 0.6 12.4": ["roaringly"], "0.8 24.0 4.9": ["ritualize"], "7.1 8.7 10.3": ["nritya"], "29.6 21.8 25.4": ["taloned"], "15.9 -4.4 -1.7": ["followingthe"], "12.2 32.5 10.4": ["unhorsed"], "1.0 18.1 30.4": ["boatmates"], "2.5 14.1 11.4": ["persisters"], "-4.3 6.8 -4.2": ["mydriatic"], "25.5 20.3 8.0": ["frankenfood"], "14.7 7.6 16.0": ["notochord"], "21.6 1.8 3.8": ["toproduce"], "10.2 -2.2 24.3": ["saskatoon"], "2.9 26.5 14.4": ["subconciously"], "12.0 14.0 20.0": ["bigmouths"], "20.9 29.3 25.2": ["tauntaun"], "10.4 7.4 0.9": ["commentry"], "4.5 -2.0 3.3": ["diphenyl"], "3.4 6.1 16.6": ["dwts"], "18.3 12.5 23.2": ["darkey"], "17.2 1.4 31.2": ["potjie"], "-2.5 9.8 4.7": ["infusional"], "1.8 1.8 3.2": ["ekantipur"], "5.0 20.4 9.5": ["supportin"], "15.6 13.2 11.9": ["woefulness"], "-13.1 10.3 -3.4": ["signator"], "-0.0 8.2 5.1": ["wanita"], "9.2 0.1 6.7": ["sugest"], "16.7 10.5 18.6": ["watertower"], "12.5 2.2 1.3": ["andt"], "9.7 3.5 11.9": ["mobileme"], "19.1 11.6 16.3": ["eatertainment"], "-1.2 14.6 1.1": ["ungifted"], "0.7 3.1 7.1": ["whem"], "10.9 20.8 14.3": ["gigglers"], "10.5 20.2 15.9": ["wardrivers"], "7.3 9.0 -2.3": ["playright"], "7.1 8.1 12.2": ["phagocytic"], "9.3 21.0 18.3": ["houris"], "-0.8 11.2 8.5": ["kinksters"], "-2.9 -1.2 5.4": ["keratoplasty"], "5.9 7.8 11.4": ["crowdpleasers"], "18.7 10.5 45.1": ["taramosalata"], "2.8 11.6 2.7": ["undersampled"], "-11.4 18.2 2.9": ["dissentions"], "6.9 14.0 5.5": ["transregional"], "5.0 13.6 29.9": ["alphonso"], "14.6 16.6 13.2": ["superbubble"], "-4.8 3.2 2.8": ["druggings"], "2.9 2.9 4.4": ["ticketline"], "-11.5 21.2 2.5": ["hadeeth"], "5.9 5.8 -0.3": ["initialising"], "8.4 6.3 5.5": ["asthetics"], "21.3 14.6 15.0": ["faddism"], "9.5 20.8 7.4": ["sourcecode"], "4.0 7.4 13.6": ["nara"], "8.2 4.7 -0.2": ["godesses"], "2.7 -4.3 -5.9": ["spokesoman"], "4.4 6.8 10.6": ["mouthrinse"], "4.6 24.0 13.4": ["contageous"], "2.5 22.0 14.2": ["tazing"], "4.8 11.0 4.1": ["sruti"], "-2.0 8.8 3.1": ["rubeola"], "6.1 13.1 11.6": ["overplotted"], "13.8 6.4 6.1": ["trumpery"], "18.0 7.8 9.2": ["tapdance"], "23.3 8.4 17.4": ["caganer"], "5.0 -1.1 31.6": ["salsiccia"], "12.9 11.3 15.5": ["plackets"], "10.1 -0.3 9.7": ["postclose"], "4.0 1.6 -3.4": ["ninties"], "12.5 23.9 19.6": ["heezy"], "11.3 11.7 19.2": ["larvicidal"], "15.7 -6.3 6.6": ["reportedy"], "11.9 11.0 8.1": ["planker"], "11.8 8.6 12.6": ["peening"], "4.2 16.3 13.7": ["foreshorten"], "5.4 5.2 7.7": ["explora"], "7.4 13.9 16.3": ["darl"], "5.8 0.6 3.7": ["showreels"], "-4.3 8.2 6.0": ["asessment"], "8.9 -5.8 11.8": ["operatorships"], "6.2 11.9 13.3": ["houngan"], "3.8 11.5 9.6": ["humic"], "4.2 11.9 7.9": ["complementaries"], "14.8 29.2 5.4": ["yomping"], "-2.6 13.3 1.7": ["hypopneas"], "11.8 30.7 10.5": ["bombsites"], "2.0 22.5 9.4": ["laughters"], "21.2 23.5 14.2": ["irresistably"], "0.5 7.7 16.6": ["rewashed"], "4.0 3.2 26.2": ["palengke"], "15.0 11.0 8.2": ["architechture"], "2.6 20.4 4.2": ["overemphasising"], "24.2 19.0 14.0": ["lazers"], "-1.5 6.6 14.0": ["takot"], "-0.9 16.3 7.0": ["ascendants"], "4.1 12.4 7.8": ["wrod"], "0.1 30.7 5.4": ["opressed"], "-7.8 10.3 14.2": ["baik"], "15.8 2.3 10.8": ["microcrystals"], "5.5 2.4 6.6": ["theaverage"], "20.1 14.3 18.2": ["colugo"], "8.4 23.4 18.4": ["hedonistically"], "5.1 3.2 20.9": ["polymorpha"], "3.7 19.3 7.5": ["faltu"], "2.7 3.8 34.3": ["briyani"], "20.5 13.1 24.4": ["unshapely"], "8.3 4.4 10.4": ["nematology"], "4.3 9.4 21.4": ["cohn"], "3.0 15.2 5.7": ["leukaemic"], "8.5 10.5 4.9": ["fastforward"], "18.6 11.9 21.6": ["haymow"], "-0.7 1.4 7.7": ["geomembranes"], "4.6 13.1 7.0": ["pluralize"], "-0.9 6.5 10.5": ["trabajar"], "5.3 12.7 5.1": ["clientelist"], "10.2 24.2 7.4": ["inquisitional"], "0.5 14.8 7.6": ["fancast"], "-2.8 12.0 3.0": ["evalute"], "19.4 24.4 20.7": ["overbalancing"], "3.8 17.0 13.1": ["cline"], "1.6 4.4 9.5": ["mediumterm"], "8.8 13.9 12.8": ["bundhs"], "-1.1 1.3 -8.1": ["distr"], "1.5 3.4 6.7": ["trioxide"], "8.2 13.7 2.6": ["communciation"], "13.2 11.8 12.9": ["twitchier"], "1.8 11.2 3.9": ["qawaali"], "7.7 0.6 7.3": ["yeop"], "10.2 8.4 -3.6": ["toom"], "-3.5 12.5 14.8": ["isaac"], "-0.8 -3.2 5.6": ["transabdominal"], "9.1 4.2 19.6": ["bistrot"], "11.1 5.5 14.3": ["bodysurfer"], "17.8 17.6 20.6": ["hawklike"], "23.7 8.9 5.6": ["displayer"], "8.3 13.0 10.7": ["millionfold"], "1.3 7.6 7.1": ["collingwood"], "3.5 10.5 10.7": ["vulns"], "7.7 4.0 7.5": ["bott"], "22.4 16.0 31.3": ["catkin"], "11.4 15.8 17.1": ["diddles"], "17.5 12.6 19.3": ["oafishness"], "-8.1 5.1 13.3": ["reklamo"], "15.8 16.0 11.5": ["supercompetitive"], "-1.3 3.4 5.3": ["testfied"], "-9.6 -1.7 -3.6": ["tert"], "3.9 13.3 17.3": ["acaricide"], "2.2 10.7 2.3": ["parapolitics"], "10.3 9.7 4.5": ["bizman"], "16.4 9.7 44.2": ["prawning"], "4.2 7.4 16.2": ["wheelwrights"], "6.0 -7.2 1.6": ["eting"], "10.6 -2.7 29.9": ["fraiche"], "-0.4 7.8 19.6": ["tinh"], "12.1 27.0 7.4": ["hissable"], "15.4 17.2 6.4": ["spacewalked"], "7.0 13.6 12.4": ["harumph"], "-4.2 2.0 1.7": ["credentialling"], "12.1 -1.2 16.0": ["sugarmaker"], "-2.4 9.1 7.6": ["myeloablative"], "7.0 14.7 -0.5": ["challanging"], "3.0 0.9 -3.8": ["gaving"], "13.4 31.5 23.6": ["woodsmanship"], "8.3 4.4 20.9": ["moun"], "5.8 5.5 4.8": ["yourname"], "2.5 4.1 10.5": ["cutis"], "20.4 10.6 16.6": ["singsongs"], "5.9 -3.9 12.5": ["overbids"], "8.8 0.3 22.9": ["chowdown"], "11.8 -2.4 12.7": ["fies"], "2.8 17.4 11.5": ["uncinematic"], "10.5 6.1 4.6": ["tardiest"], "6.1 -4.5 0.7": ["centr"], "10.9 4.0 23.3": ["lumpers"], "10.8 7.5 4.0": ["ashington"], "3.3 19.1 14.5": ["beyotch"], "10.9 4.5 5.0": ["nanomanipulation"], "14.2 2.6 17.8": ["hardanger"], "9.3 5.9 12.0": ["stipe"], "1.9 11.2 17.8": ["swin"], "10.3 13.1 11.0": ["bluesology"], "-7.1 12.2 5.9": ["nonpsychiatric"], "13.7 1.2 6.4": ["teraelectronvolts"], "10.2 10.6 11.2": ["revhead"], "7.4 18.1 7.5": ["polylines"], "1.8 11.2 4.3": ["venters"], "7.1 7.0 9.2": ["kustom"], "5.0 14.4 12.0": ["buttinsky"], "2.6 7.7 7.2": ["xavi"], "19.7 11.5 5.5": ["saddos"], "19.7 4.0 28.9": ["ponga"], "-2.1 -1.5 3.3": ["chorographer"], "9.7 10.9 16.5": ["manservants"], "0.5 3.7 4.9": ["mith"], "6.8 5.2 18.8": ["especiales"], "2.7 10.0 32.4": ["sheening"], "15.0 18.1 25.8": ["glissade"], "11.3 4.1 1.9": ["erreicht"], "21.8 37.1 0.7": ["cyberterrorist"], "2.7 -9.1 10.2": ["drystock"], "22.2 7.5 11.7": ["sniffin"], "-1.6 -4.1 -0.6": ["presidnet"], "8.4 7.2 6.4": ["modifed"], "-4.2 3.4 5.6": ["breifing"], "0.9 14.0 17.7": ["unseaworthiness"], "0.9 11.0 3.5": ["medicade"], "15.7 30.2 9.2": ["revenger"], "20.4 12.7 14.4": ["piccaninnies"], "11.6 14.0 41.7": ["tacklebox"], "12.8 18.7 9.4": ["middlweight"], "1.4 18.2 4.7": ["affectional"], "3.6 9.4 19.3": ["baro"], "-3.4 18.6 4.2": ["kavod"], "14.8 12.9 17.0": ["piler"], "3.7 10.3 10.6": ["lega"], "-5.0 10.1 -0.8": ["unconsented"], "5.5 14.4 -1.7": ["criticsed"], "-1.2 9.5 -3.9": ["communiqui"], "3.8 10.5 32.2": ["whitewing"], "10.1 0.6 7.2": ["ferrochromium"], "12.5 15.9 2.2": ["climbdowns"], "3.8 7.0 -3.0": ["reated"], "11.4 3.3 16.8": ["coiffeurs"], "-0.1 3.8 8.1": ["quinones"], "8.1 15.0 14.6": ["honeynet"], "11.1 6.0 3.0": ["andnon"], "3.4 14.6 8.3": ["coactivators"], "6.6 3.5 -1.1": ["profesionals"], "5.1 1.1 -4.0": ["administator"], "5.5 10.6 22.9": ["mumming"], "10.5 12.4 11.2": ["versifier"], "10.8 12.5 1.7": ["secutiry"], "6.3 9.2 8.6": ["boubou"], "11.8 27.5 12.5": ["mentallity"], "6.0 -0.2 6.7": ["sharings"], "15.3 13.1 20.0": ["sheppard"], "7.8 4.8 6.2": ["actionscript"], "10.0 1.9 10.6": ["bedford"], "7.8 14.4 12.9": ["sphinxlike"], "4.8 9.5 7.2": ["unsafeguarded"], "17.5 11.4 19.5": ["jetter"], "2.0 20.8 -0.0": ["mechitza"], "16.0 1.8 23.4": ["palmiers"], "8.6 19.7 8.8": ["chelas"], "-2.7 -3.6 -7.8": ["stablished"], "9.7 1.7 8.1": ["dichos"], "-6.8 -5.8 7.5": ["imme"], "21.6 16.2 25.9": ["fatsia"], "9.6 9.8 9.3": ["conner"], "6.3 4.0 18.5": ["treescape"], "9.9 9.6 3.9": ["evenmore"], "2.0 1.6 11.4": ["recursos"], "8.7 18.1 11.3": ["blackie"], "5.5 20.1 2.9": ["banlieus"], "-3.2 -4.6 5.6": ["brith"], "25.2 9.1 13.2": ["gearmakers"], "6.3 2.5 10.4": ["pearlite"], "7.6 -6.2 23.6": ["carageenan"], "10.4 6.1 15.0": ["rastafarian"], "20.2 19.9 12.4": ["pixelized"], "4.0 0.5 10.2": ["sph"], "20.7 21.7 5.0": ["graviton"], "16.3 1.1 4.5": ["biomedicines"], "3.8 22.1 7.4": ["leagued"], "8.0 4.5 0.4": ["tokenisation"], "13.7 6.0 30.3": ["ciabattas"], "5.3 13.3 7.5": ["earthness"], "16.6 12.6 24.0": ["cereus"], "10.3 3.6 15.8": ["morula"], "-6.2 6.4 2.7": ["farbrengen"], "13.4 23.4 9.2": ["supernaturals"], "3.0 14.6 9.1": ["economicconditions"], "9.8 8.8 7.6": ["hospitalises"], "4.1 5.1 -0.1": ["ecc"], "8.4 9.6 6.3": ["recognisability"], "9.2 17.1 12.1": ["microlite"], "2.4 9.7 13.2": ["eocnomy"], "14.5 10.8 2.5": ["miniaturizes"], "19.6 15.1 13.0": ["catatonically"], "8.3 11.8 3.2": ["hoch"], "10.5 14.5 36.2": ["panchan"], "7.3 6.1 9.4": ["reserpine"], "1.2 15.3 22.2": ["temperture"], "9.4 12.6 1.3": ["denouncer"], "5.1 1.8 -4.6": ["creedence"], "8.4 -4.5 0.0": ["talkes"], "5.9 9.4 12.2": ["ouabain"], "10.1 2.0 10.3": ["unathorised"], "-3.5 24.8 9.2": ["aperson"], "11.8 15.1 21.6": ["blueing"], "24.5 35.8 22.6": ["xenomorph"], "3.7 -0.6 5.8": ["vuelta"], "15.0 -2.0 5.5": ["cippe"], "11.6 21.4 7.2": ["nonoffensive"], "11.8 13.9 9.7": ["monotonal"], "-1.9 4.4 11.8": ["pae"], "4.8 22.3 5.1": ["whiplashes"], "7.8 13.9 14.1": ["mentum"], "13.7 7.7 21.8": ["yok"], "9.4 11.0 21.7": ["dixon"], "5.3 9.6 12.9": ["antisera"], "3.0 11.9 6.7": ["ndp"], "17.1 8.0 9.5": ["crippleware"], "7.4 -8.4 7.8": ["bobl"], "4.3 12.3 3.4": ["vulgarised"], "13.6 6.6 37.0": ["flauta"], "-10.5 4.5 2.7": ["relapser"], "17.4 3.7 11.8": ["cybercity"], "3.6 1.9 12.2": ["dihydroxyacetone"], "8.3 0.8 4.1": ["includs"], "10.4 2.1 5.2": ["objetivo"], "-5.4 -1.2 10.8": ["cashspiels"], "-0.9 6.0 7.2": ["preppiness"], "16.7 15.8 12.5": ["beaurocratic"], "6.2 6.9 5.5": ["podocyte"], "-9.4 5.1 2.3": ["recomputation"], "6.7 3.8 1.9": ["devient"], "1.6 -6.8 1.5": ["dimanche"], "21.4 9.3 5.3": ["errected"], "14.6 3.6 -3.9": ["subbrand"], "16.4 19.7 16.5": ["endplay"], "-0.5 6.1 1.0": ["acadamy"], "-2.0 -2.4 -12.2": ["countersigning"], "17.9 10.1 32.0": ["transhipping"], "8.5 0.9 6.1": ["farmacia"], "17.1 15.6 5.7": ["hyperfast"], "7.7 6.7 4.0": ["clastics"], "3.4 12.5 14.2": ["stepyourgameup"], "2.8 6.8 14.8": ["enny"], "14.9 3.7 11.4": ["prestrike"], "-4.2 -5.5 6.6": ["uction"], "-8.1 16.8 5.3": ["midle"], "5.2 1.3 9.0": ["geothermally"], "0.8 24.6 7.9": ["playtests"], "13.8 8.5 15.3": ["alembic"], "8.7 11.4 22.0": ["fossilisation"], "6.3 2.7 4.7": ["nightlies"], "16.3 6.9 9.9": ["sytle"], "2.2 21.2 4.0": ["perceivers"], "7.1 13.9 1.1": ["ramdisk"], "9.0 2.2 8.3": ["valeur"], "-6.1 6.2 6.6": ["touchowns"], "15.7 4.2 32.7": ["jellyroll"], "8.7 15.0 14.7": ["overspin"], "5.3 9.0 12.1": ["ruk"], "3.7 3.2 21.9": ["brunswick"], "17.4 8.3 39.1": ["tamarillos"], "-4.3 12.3 17.7": ["expeditures"], "0.0 6.2 17.0": ["gyod"], "11.2 10.5 18.0": ["monochromatically"], "2.0 23.5 0.0": ["unwavered"], "9.8 7.8 7.7": ["paanwala"], "2.4 6.2 1.0": ["playd"], "4.1 16.8 9.1": ["threathened"], "1.8 5.2 12.0": ["subdividers"], "3.1 8.3 16.4": ["midcity"], "7.7 14.8 -0.5": ["bancor"], "6.3 -5.0 -3.5": ["hemo"], "-2.7 7.9 1.9": ["concessionality"], "16.3 10.8 7.1": ["gassifier"], "1.2 4.6 19.0": ["morni"], "2.3 8.7 0.0": ["mesolimbic"], "18.8 7.6 2.6": ["eyevis"], "19.1 20.2 0.6": ["pyrotechnically"], "1.6 -7.1 3.5": ["preregistrations"], "2.4 3.9 3.8": ["mnt"], "-6.6 -4.1 9.0": ["superintedent"], "4.7 23.5 8.1": ["autoexposure"], "2.9 6.8 16.4": ["sarcoids"], "18.1 16.9 16.9": ["chokeslamming"], "8.6 11.5 12.4": ["lilke"], "2.8 10.4 12.3": ["superfetation"], "10.3 22.0 18.5": ["djturtleface"], "2.8 5.3 11.4": ["moderato"], "24.3 14.2 28.0": ["munchable"], "-2.7 11.7 8.6": ["fulfulling"], "4.8 9.6 23.2": ["recontaminated"], "3.5 2.1 7.4": ["tarana"], "2.7 12.5 7.3": ["cursus"], "3.1 11.7 14.0": ["raagas"], "3.0 14.9 3.4": ["munda"], "1.4 27.8 8.1": ["proudness"], "5.6 4.0 0.4": ["fillups"], "6.2 18.9 12.6": ["clichd"], "9.5 9.6 21.6": ["cebu"], "-0.7 5.1 7.9": ["basilar"], "16.2 -6.4 5.4": ["facilitiy"], "11.3 5.8 10.9": ["vonage"], "14.9 12.7 23.1": ["coble"], "11.5 7.2 22.9": ["ashlar"], "6.5 6.3 8.7": ["qmail"], "-1.1 4.2 7.1": ["vehichle"], "24.6 4.7 24.9": ["plinko"], "14.4 4.3 14.5": ["mastics"], "14.0 7.0 0.1": ["denigratory"], "3.7 0.7 8.7": ["confce"], "9.7 3.4 6.5": ["semba"], "17.9 13.7 40.1": ["queenfish"], "17.1 1.0 -6.6": ["arecent"], "12.8 2.9 37.2": ["fonduta"], "2.1 32.2 8.7": ["damnest"], "12.3 2.9 6.0": ["invt"], "1.9 -7.9 3.6": ["cpn"], "-8.2 -4.0 -7.4": ["kcur"], "-8.1 -1.8 3.0": ["montessori"], "12.5 11.3 17.2": ["nightscapes"], "1.8 4.4 9.9": ["waith"], "5.2 5.7 8.9": ["midfieler"], "2.0 11.7 12.3": ["protozoal"], "11.0 22.8 9.8": ["backstep"], "12.9 7.4 14.3": ["dairyland"], "8.2 -5.9 9.5": ["conflab"], "-7.2 8.7 0.6": ["srinagar"], "2.2 -2.6 8.6": ["pio"], "3.3 2.8 10.6": ["tance"], "11.1 17.9 6.0": ["fabulism"], "14.5 20.4 5.6": ["unprotectable"], "8.3 14.3 48.0": ["sandfleas"], "14.6 6.2 14.2": ["twanger"], "11.5 0.4 6.5": ["multivision"], "-5.9 12.2 3.1": ["irrate"], "7.4 21.2 5.9": ["capabilty"], "15.8 19.3 23.8": ["wenching"], "7.1 1.0 10.4": ["puente"], "6.8 5.6 3.7": ["hopefulls"], "7.1 4.8 11.1": ["enorme"], "0.8 2.6 10.2": ["queryable"], "2.0 9.7 20.8": ["ahupuaa"], "0.5 8.0 2.6": ["oses"], "-5.7 -4.0 -3.6": ["ental"], "3.8 20.0 11.3": ["vehical"], "-1.3 6.0 2.7": ["gemifloxacin"], "23.1 9.6 -0.2": ["anticompetition"], "1.9 9.6 30.2": ["woodier"], "5.5 -5.1 1.9": ["subconsultant"], "6.7 10.1 15.7": ["usda"], "6.3 6.5 9.1": ["desoldering"], "4.4 16.4 7.1": ["suppposed"], "4.6 9.5 13.2": ["stocktheft"], "1.8 17.3 -3.7": ["combustions"], "6.9 13.9 15.8": ["shir"], "19.3 -1.7 1.1": ["nology"], "16.6 9.8 28.4": ["saltmarshes"], "1.7 4.4 15.5": ["kulhadd"], "15.6 10.2 40.4": ["bloater"], "8.2 3.9 11.6": ["cantante"], "3.6 14.1 -5.7": ["organisaton"], "0.1 12.5 4.2": ["sistem"], "2.3 7.7 12.4": ["faut"], "11.7 13.7 16.8": ["womanish"], "4.2 10.6 43.5": ["groundfishery"], "5.1 10.3 11.4": ["unromantically"], "15.0 9.7 26.2": ["egusi"], "7.7 6.1 23.2": ["undercoats"], "2.7 19.5 5.0": ["microtrauma"], "18.3 11.6 24.4": ["tyrannosaurids"], "8.4 5.3 20.2": ["hotrolled"], "7.3 -0.2 -0.4": ["winover"], "6.6 15.4 14.5": ["winze"], "2.3 3.0 -1.1": ["rifalazil"], "-0.8 1.0 4.0": ["untl"], "15.2 18.5 2.3": ["strategems"], "16.6 9.1 30.7": ["protist"], "0.9 7.6 7.2": ["changements"], "16.8 23.5 12.2": ["tepui"], "9.3 18.5 19.0": ["enzo"], "11.3 3.3 24.0": ["ajwain"], "16.6 3.5 7.9": ["incombustible"], "8.3 20.9 4.5": ["tehre"], "-1.2 5.0 7.0": ["recertifies"], "10.9 6.4 8.3": ["underbuilt"], "9.6 20.7 8.4": ["undateable"], "14.4 5.4 39.2": ["hookbait"], "0.6 5.6 7.1": ["pointsand"], "10.0 14.1 23.1": ["streetsweeper"], "-4.9 4.3 -5.3": ["relat"], "0.7 0.6 13.9": ["nongamblers"], "1.0 7.7 19.4": ["tuwing"], "11.6 11.7 5.7": ["fdisk"], "-1.4 -2.0 -7.3": ["affiars"], "13.5 10.1 15.1": ["stroboscope"], "6.6 16.9 7.0": ["apporach"], "11.1 20.3 16.8": ["meand"], "0.7 12.1 7.7": ["umms"], "12.3 2.3 17.6": ["cubana"], "5.8 4.1 5.8": ["azides"], "1.4 12.4 5.4": ["atovaquone"], "3.2 2.8 3.9": ["withrespect"], "8.4 10.9 11.8": ["argentino"], "9.7 3.3 0.8": ["manganite"], "5.3 12.0 14.8": ["artspeak"], "12.7 3.8 9.3": ["divy"], "-1.8 0.5 7.1": ["ahk"], "9.7 7.0 8.4": ["semiautomated"], "10.8 18.1 21.0": ["hearthside"], "4.0 -1.8 19.8": ["adularia"], "7.6 25.6 9.0": ["demagoging"], "9.6 14.2 6.0": ["radiograms"], "13.9 17.1 6.4": ["disgrunted"], "7.1 14.1 16.5": ["saggers"], "5.2 1.4 6.2": ["sergio"], "-5.7 7.7 -0.5": ["dimunition"], "11.2 3.5 14.0": ["autoharps"], "-1.0 16.8 20.8": ["winterlike"], "7.0 17.8 1.6": ["freeflow"], "4.7 13.0 11.7": ["submersions"], "8.4 16.0 21.1": ["chloejn"], "8.3 10.8 6.1": ["qawali"], "14.5 8.6 14.9": ["dawdler"], "17.8 0.6 6.2": ["popstress"], "-5.8 13.6 -0.8": ["integrities"], "16.4 11.6 17.7": ["floodable"], "-2.6 13.4 -6.7": ["erros"], "0.4 9.2 20.9": ["perfumy"], "10.9 -5.4 13.3": ["bwah"], "10.2 13.5 12.9": ["ettiquette"], "25.6 10.9 24.7": ["crenellations"], "20.1 0.6 11.5": ["elecricity"], "16.4 35.2 11.3": ["thanes"], "9.0 15.3 0.8": ["ludicrious"], "6.9 -7.1 -0.4": ["imes"], "17.9 14.4 13.4": ["taskbars"], "19.9 3.3 14.9": ["chicos"], "17.8 8.9 20.7": ["krap"], "-2.4 -1.0 -2.1": ["trisodium"], "-9.3 2.0 7.6": ["magistrated"], "16.5 6.3 18.6": ["bonging"], "0.7 22.6 9.5": ["burnovers"], "8.7 19.2 7.9": ["hotlinking"], "-4.2 -0.1 9.3": ["rearraigned"], "1.2 -3.2 6.4": ["lla"], "4.0 11.1 13.8": ["quadding"], "8.3 7.2 16.3": ["stockton"], "-0.3 7.4 15.2": ["tupe"], "14.3 27.4 12.1": ["sigils"], "15.1 26.9 10.0": ["mmfa"], "13.7 2.7 -9.6": ["parterships"], "0.9 13.0 14.7": ["enjo"], "4.0 -2.8 -7.5": ["alumini"], "3.4 -0.3 -3.5": ["minidisk"], "-4.4 6.3 9.3": ["ledoff"], "6.4 1.3 -0.3": ["diffractometer"], "2.7 0.2 13.7": ["gigi"], "6.9 11.6 10.8": ["extraordinarly"], "1.5 14.3 14.7": ["politiqueras"], "-1.6 4.0 0.3": ["accessioning"], "17.1 15.6 27.9": ["hawkweed"], "8.2 6.5 2.6": ["unreceipted"], "9.5 -8.9 5.1": ["nonlisted"], "4.8 21.3 0.4": ["assylum"], "14.4 12.1 8.6": ["antiregulatory"], "17.8 4.2 5.3": ["transglobal"], "-8.0 12.2 4.2": ["univocally"], "4.8 4.8 23.1": ["ipu"], "1.1 0.8 14.6": ["soni"], "5.6 9.6 14.0": ["nahm"], "3.9 11.9 15.9": ["foulfest"], "-5.4 13.9 -3.3": ["complimentarily"], "14.1 13.8 38.8": ["paillard"], "12.7 16.1 10.2": ["crucifiction"], "7.0 5.3 -3.7": ["dowloaded"], "-2.4 18.0 6.8": ["fictionalising"], "7.3 15.3 10.6": ["interrelates"], "9.0 14.3 19.0": ["vere"], "14.9 13.8 32.1": ["bullfinches"], "7.7 -4.0 5.6": ["mandocello"], "11.8 6.0 9.6": ["fieldturf"], "11.2 -2.5 -11.7": ["ihas"], "3.7 8.6 5.4": ["orignial"], "14.7 10.0 12.3": ["slackly"], "11.6 15.9 20.5": ["topspinner"], "6.3 -5.6 -2.7": ["exepected"], "-0.8 13.2 4.4": ["recopy"], "-3.6 2.1 -0.7": ["teleconsultation"], "14.8 14.5 14.2": ["expectorated"], "0.3 -4.9 5.4": ["dentention"], "6.8 1.0 9.5": ["melton"], "15.8 10.2 13.3": ["horrorfest"], "-6.1 2.8 3.8": ["detials"], "5.4 6.9 6.4": ["sociolinguistic"], "13.6 13.9 12.2": ["rudimental"], "7.3 5.7 6.4": ["crosssection"], "-2.8 5.0 6.2": ["naina"], "2.8 13.8 15.3": ["pahgre"], "12.4 15.6 12.3": ["oooohs"], "8.4 23.6 13.5": ["idiosyncracy"], "8.4 21.6 10.2": ["disbeliefs"], "11.0 6.1 12.9": ["prototypal"], "15.3 14.3 12.4": ["microworld"], "12.3 0.1 9.5": ["commmercial"], "9.2 -1.9 -5.1": ["dixit"], "6.9 14.5 15.7": ["scatterplot"], "7.4 13.7 8.7": ["onloan"], "27.2 6.0 9.9": ["kronors"], "0.5 -0.9 7.2": ["oxidations"], "-10.4 9.6 3.4": ["holydays"], "7.4 22.9 8.6": ["uncensorable"], "5.6 47.1 2.0": ["psyop"], "8.0 0.1 14.7": ["rhoi"], "7.1 5.6 11.3": ["hookin"], "-3.3 19.0 1.5": ["jazia"], "12.3 7.5 7.4": ["overgeared"], "4.4 20.5 8.7": ["ussr"], "-0.4 3.0 7.9": ["subhed"], "15.4 5.7 32.1": ["candylike"], "4.4 9.3 -3.4": ["psephology"], "-4.9 -5.7 3.6": ["saidshe"], "-1.3 4.8 8.1": ["martensitic"], "15.6 6.0 16.7": ["galvanizer"], "-2.8 19.0 -1.3": ["overwelming"], "5.6 11.5 10.1": ["kjkjkjkk"], "7.2 16.4 9.8": ["tepidness"], "19.2 11.3 36.4": ["sportfishers"], "6.5 3.1 6.7": ["grandmum"], "2.0 -1.4 3.5": ["financia"], "4.9 8.5 11.8": ["maunga"], "-3.4 15.3 5.0": ["collogues"], "16.7 -0.2 30.6": ["turduckens"], "2.7 13.6 32.9": ["redpoll"], "0.1 12.8 7.1": ["micronuclei"], "-0.3 7.5 4.2": ["gren"], "-3.2 12.9 2.8": ["getthe"], "11.8 -0.6 8.5": ["quasipublic"], "20.8 6.0 10.9": ["scarpering"], "-4.3 13.3 0.5": ["elucidations"], "13.6 11.1 16.3": ["peopleto"], "9.5 18.1 2.5": ["purusing"], "7.2 19.9 5.2": ["stropping"], "18.7 15.7 13.5": ["towbars"], "4.4 6.4 10.1": ["wiehed"], "-2.1 7.2 14.8": ["embryonal"], "10.5 11.2 23.4": ["scamble"], "-7.6 14.1 10.2": ["rupa"], "26.2 11.5 14.4": ["crossbone"], "4.9 3.6 1.5": ["lifecyle"], "4.9 11.2 13.0": ["neighborhoody"], "21.1 5.7 27.0": ["wobbegong"], "18.8 14.4 28.9": ["oversweet"], "17.0 16.8 15.5": ["gaspers"], "6.4 6.6 16.6": ["xiangsheng"], "6.2 17.7 6.6": ["administraion"], "7.6 11.7 11.9": ["arjun"], "1.5 -2.8 5.7": ["secteur"], "4.6 6.1 -0.8": ["gradable"], "8.6 14.3 17.0": ["selembu"], "7.2 10.5 13.7": ["flirtiness"], "-5.8 -0.9 7.4": ["prosthodontists"], "5.2 23.2 0.4": ["overwatching"], "12.1 4.6 3.0": ["pof"], "-1.2 -3.0 4.3": ["raceoff"], "-8.5 2.8 8.4": ["seveth"], "4.3 7.8 2.6": ["gliderport"], "6.9 4.7 7.6": ["welches"], "4.0 -1.3 9.6": ["monophosphate"], "7.0 18.5 14.6": ["picutre"], "6.5 9.4 16.7": ["juryo"], "5.4 6.7 12.2": ["psoralen"], "2.3 -1.2 9.8": ["heure"], "9.2 15.1 4.9": ["mythbusting"], "21.0 14.1 16.0": ["tinies"], "11.1 7.9 25.7": ["latkas"], "18.8 14.4 7.7": ["acquisitor"], "-3.5 -0.4 10.2": ["theearly"], "3.9 4.9 25.1": ["spikedace"], "9.9 12.2 11.6": ["barfight"], "2.2 3.3 11.8": ["dejjem"], "-3.9 8.7 4.3": ["rasas"], "10.9 13.8 8.1": ["enogh"], "4.7 7.4 0.9": ["thrombosed"], "5.5 5.9 5.8": ["crystallographers"], "11.3 13.0 9.0": ["allmost"], "8.7 1.1 8.5": ["bestellen"], "5.0 6.2 9.8": ["headscratching"], "4.0 3.6 11.1": ["ukn"], "8.8 0.7 12.7": ["bodycon"], "10.3 1.1 3.6": ["mortagage"], "21.5 13.2 30.4": ["candled"], "-3.4 14.6 4.7": ["xxxiii"], "2.9 9.1 4.9": ["ldap"], "3.8 -0.5 19.8": ["ganji"], "0.3 -3.0 -5.6": ["protel"], "-3.6 8.4 7.8": ["retainable"], "3.6 2.7 14.0": ["marilyn"], "1.6 14.3 7.6": ["ecumenists"], "3.4 21.2 5.4": ["endued"], "14.9 6.7 13.5": ["doumbek"], "16.9 14.3 20.2": ["tulou"], "1.4 12.4 15.4": ["nurdled"], "4.6 17.6 3.8": ["windblast"], "8.0 -0.2 13.1": ["milagro"], "11.8 6.3 12.8": ["daniels"], "9.7 13.8 0.7": ["subrogate"], "10.1 -2.3 1.4": ["prepration"], "4.9 5.7 7.8": ["hess"], "3.8 10.6 21.4": ["freshets"], "4.1 -2.0 14.0": ["dree"], "3.2 10.7 4.0": ["neurodermatitis"], "0.9 -4.4 11.5": ["indiction"], "3.9 17.1 10.9": ["councilpeople"], "4.4 27.9 10.4": ["egyptians"], "13.7 1.2 23.4": ["tahina"], "23.2 -1.7 -0.6": ["unscrubbed"], "0.9 7.4 10.2": ["moyen"], "1.2 4.9 0.7": ["acception"], "13.5 -2.7 13.4": ["surfine"], "13.0 14.7 13.0": ["luvvy"], "4.9 14.7 30.0": ["croppings"], "9.0 17.1 8.2": ["celebratin"], "10.3 19.2 20.7": ["inyour"], "2.7 16.1 0.4": ["mabahith"], "4.5 30.9 11.6": ["embattlement"], "6.1 21.1 3.5": ["confabulate"], "1.5 9.4 3.7": ["hotplug"], "8.9 2.5 13.5": ["rackmounted"], "-1.5 8.1 10.1": ["alcoholically"], "19.9 7.8 22.8": ["lucious"], "8.2 12.5 7.9": ["equ"], "8.8 7.0 4.3": ["metaglidasen"], "3.8 7.5 4.7": ["cytometer"], "3.3 18.4 10.6": ["shanny"], "-0.4 11.4 4.2": ["endosonography"], "11.6 10.0 12.5": ["downtuned"], "-8.5 11.8 2.7": ["asto"], "2.2 -8.1 -4.5": ["hairman"], "-4.6 -5.3 3.4": ["addi"], "7.7 7.1 8.3": ["pyrabactin"], "8.1 10.8 2.7": ["resoling"], "9.1 -1.5 8.7": ["polybutadiene"], "6.9 3.8 13.0": ["dvi"], "4.0 9.1 5.4": ["fto"], "24.2 9.4 -2.7": ["multidivisional"], "7.5 4.7 7.4": ["falt"], "7.5 11.9 9.4": ["lokpal"], "10.0 8.8 13.9": ["bootee"], "3.0 24.0 4.9": ["kinesthetically"], "17.1 12.3 6.7": ["trepanning"], "2.1 14.5 6.8": ["japa"], "11.1 10.6 5.8": ["catastrophists"], "0.4 5.1 6.7": ["ovetime"], "13.6 6.7 7.0": ["gemaakt"], "12.0 11.0 6.2": ["adblock"], "9.6 17.8 19.1": ["doult"], "10.2 17.0 20.8": ["unroped"], "1.2 19.3 9.4": ["ibadah"], "-4.6 12.7 8.3": ["vivas"], "11.0 10.3 -5.2": ["simyo"], "11.8 7.9 22.8": ["scooby"], "14.9 10.3 44.4": ["candlefish"], "9.5 21.1 11.4": ["adultress"], "4.5 4.1 9.9": ["degazette"], "0.3 -2.5 1.8": ["meetng"], "5.9 25.6 4.5": ["kurdish"], "31.4 3.4 2.9": ["demerges"], "0.9 13.9 11.2": ["stressfulness"], "14.5 7.4 25.8": ["champurrado"], "-7.2 1.2 14.8": ["subwatershed"], "8.8 -0.8 2.0": ["gamechanging"], "8.0 -0.5 15.8": ["tyne"], "7.9 22.5 7.5": ["ecumenicalism"], "22.3 -1.4 7.0": ["gentrader"], "19.1 2.9 12.0": ["armonica"], "8.0 8.6 29.0": ["kuri"], "7.1 4.3 5.1": ["underdoing"], "8.5 5.7 17.1": ["vg"], "19.6 10.4 6.4": ["cartelized"], "14.7 6.0 22.6": ["raceboat"], "6.4 -0.5 31.1": ["tripas"], "19.7 19.1 3.8": ["greenwashers"], "12.9 2.2 29.3": ["sandwhiches"], "7.8 6.3 12.3": ["consitently"], "13.8 1.8 10.5": ["polybutylene"], "9.5 7.0 1.6": ["clienteling"], "5.0 15.3 2.3": ["unstability"], "5.9 5.1 12.5": ["muslins"], "10.1 9.4 9.0": ["powerpole"], "25.2 19.7 10.9": ["megatron"], "7.3 8.5 9.9": ["subdials"], "-0.5 -7.1 1.1": ["cmp"], "2.2 5.6 15.7": ["beels"], "16.0 7.6 11.6": ["diski"], "-1.5 9.9 9.9": ["tappa"], "-2.4 3.9 10.5": ["ceruloplasmin"], "7.0 10.0 8.4": ["associatively"], "-10.1 4.0 3.0": ["reimprisoned"], "11.4 8.8 4.1": ["tegra"], "1.8 -0.0 5.4": ["competively"], "3.2 4.1 9.2": ["usuario"], "12.0 15.0 24.2": ["pulmonaria"], "5.4 2.7 10.7": ["osteoperosis"], "9.0 14.0 0.3": ["tetherless"], "0.4 10.1 1.8": ["kils"], "4.7 14.6 8.7": ["microearthquakes"], "4.4 -1.1 1.5": ["mediacenter"], "14.3 8.9 11.2": ["grungers"], "3.3 -2.5 0.3": ["wenty"], "8.7 4.3 27.7": ["coq"], "-1.2 5.5 8.1": ["myometrium"], "19.2 11.8 18.3": ["horlicks"], "10.2 6.8 29.6": ["tomme"], "5.0 11.0 -4.7": ["stengthen"], "3.0 9.7 9.6": ["jadoo"], "9.0 12.2 4.8": ["imazapyr"], "-3.6 11.2 9.3": ["happenend"], "20.3 10.8 5.1": ["spiffiest"], "2.7 0.5 22.8": ["herbe"], "16.2 12.9 30.4": ["forepeak"], "5.2 11.5 5.4": ["redub"], "21.3 9.4 -2.0": ["cyrillic"], "18.3 11.0 9.8": ["frathouse"], "-2.6 12.8 10.9": ["purohit"], "5.4 14.9 5.5": ["praja"], "6.8 2.3 9.2": ["patternmaker"], "2.2 12.3 -7.4": ["familiarises"], "8.8 20.0 4.7": ["thralldom"], "11.2 17.7 13.4": ["multiculture"], "8.4 4.6 -2.8": ["seriesof"], "10.0 9.2 13.6": ["curette"], "4.0 -3.7 5.2": ["scottishathletics"], "4.4 9.3 5.2": ["supersymmetric"], "16.3 2.5 27.1": ["cassavas"], "16.9 5.5 12.3": ["bedplate"], "11.3 7.8 -8.0": ["pedophelia"], "6.2 4.7 -4.9": ["theyhad"], "16.5 42.8 10.9": ["orks"], "7.3 21.6 11.4": ["sabatoge"], "19.6 19.9 12.6": ["wretching"], "-0.5 -1.0 5.0": ["competi"], "-2.7 4.0 3.6": ["dollarwise"], "8.5 25.7 13.8": ["pistoleros"], "-3.3 0.1 8.6": ["pledger"], "4.7 8.5 8.0": ["luch"], "0.9 9.9 15.7": ["akala"], "-6.0 4.2 5.8": ["ioctl"], "14.9 16.8 1.7": ["avictory"], "0.7 11.0 -0.7": ["chemometric"], "3.2 9.7 15.0": ["betts"], "-5.1 6.1 13.8": ["ebidensya"], "11.7 8.6 7.2": ["hybird"], "32.3 2.6 4.8": ["takoever"], "5.8 12.3 12.1": ["urinators"], "3.4 3.5 12.5": ["safet"], "17.7 6.8 26.0": ["bioaccumulates"], "16.6 -0.5 8.7": ["agbiotech"], "6.5 4.8 13.2": ["acht"], "0.6 14.6 12.8": ["mijo"], "7.0 -2.4 -1.3": ["carred"], "-1.5 19.3 3.2": ["damager"], "9.1 9.8 26.0": ["hazels"], "4.5 19.8 -3.9": ["legitimatized"], "16.6 4.7 23.2": ["paillette"], "3.3 10.0 9.2": ["nondollar"], "4.1 -6.3 1.4": ["theshow"], "14.6 7.5 19.2": ["camauro"], "1.7 6.7 0.8": ["parl"], "21.7 -2.0 4.9": ["rede"], "18.6 14.5 -2.8": ["carbuyers"], "3.9 42.2 3.4": ["thewar"], "6.5 11.6 9.8": ["donovan"], "18.5 17.2 17.9": ["conficker"], "9.6 -5.7 10.9": ["allweather"], "13.3 -0.9 9.6": ["methylamines"], "5.8 4.4 15.3": ["toit"], "19.7 30.6 8.4": ["nucelar"], "6.0 17.5 7.0": ["rolleyes"], "10.3 10.5 20.2": ["penitentes"], "8.8 8.8 12.4": ["jare"], "-0.0 11.4 8.8": ["underload"], "19.5 16.7 25.1": ["rustbucket"], "0.8 13.8 14.7": ["chaka"], "12.6 16.0 11.9": ["mechanising"], "-1.8 3.5 -4.6": ["electrodiagnostic"], "9.0 2.5 5.8": ["bizzarely"], "19.4 15.7 22.4": ["aucuba"], "6.8 13.7 10.7": ["microsaccades"], "5.8 2.0 6.5": ["pinsetters"], "16.0 -3.8 7.7": ["feevee"], "4.1 23.6 10.6": ["aimer"], "5.6 1.6 11.0": ["airpot"], "10.5 12.8 13.8": ["jawlines"], "-3.4 7.9 5.2": ["unruptured"], "9.2 16.4 23.9": ["ciliates"], "13.3 7.9 24.8": ["parrilla"], "6.9 6.6 5.5": ["virosome"], "-1.3 6.0 6.5": ["effectivement"], "-0.0 13.8 0.1": ["jaziya"], "-2.0 2.5 10.6": ["jerome"], "9.7 7.9 12.8": ["machiya"], "-7.9 22.9 2.3": ["preachment"], "0.3 5.2 6.2": ["sujet"], "7.0 12.3 5.8": ["riduculous"], "-0.0 13.7 6.3": ["optionholder"], "1.4 -0.7 1.3": ["ezlase"], "15.0 22.1 18.8": ["lampstand"], "11.3 5.0 8.1": ["alsobe"], "16.7 4.9 10.8": ["outter"], "-4.8 15.8 5.8": ["aru"], "1.6 9.2 -8.4": ["borad"], "12.8 7.8 13.7": ["wec"], "-2.8 9.1 10.5": ["husand"], "8.8 4.0 15.7": ["kyunki"], "26.1 18.4 12.8": ["robotlike"], "14.0 18.7 14.1": ["dankest"], "10.6 6.4 7.7": ["moeten"], "10.2 2.1 9.8": ["jornada"], "6.0 5.9 15.7": ["matzahs"], "8.4 15.8 8.9": ["nottie"], "0.4 22.6 7.2": ["resonsibility"], "20.1 3.4 14.7": ["stogy"], "17.6 8.3 20.0": ["glassfibre"], "7.5 14.0 19.0": ["rainsuit"], "2.2 5.2 2.5": ["therewere"], "5.5 9.4 5.4": ["hii"], "7.3 3.9 7.4": ["exceded"], "27.1 25.4 19.1": ["scarer"], "6.2 0.6 9.1": ["curtainsiders"], "9.9 5.6 1.6": ["semiotician"], "13.5 0.3 15.8": ["aluminous"], "21.7 15.9 11.2": ["hercules"], "10.6 5.5 13.4": ["numa"], "0.6 5.9 -0.6": ["iafrica"], "0.8 14.2 15.9": ["myosins"], "7.4 6.7 11.2": ["faregates"], "2.9 -2.3 9.2": ["desulfurizer"], "14.7 19.1 16.0": ["unstacking"], "13.4 11.5 14.3": ["carabineers"], "5.1 3.4 17.0": ["boses"], "5.7 8.7 20.8": ["sprigging"], "3.7 -3.2 7.0": ["etoile"], "1.4 3.2 15.7": ["aberdeen"], "-1.3 -0.9 11.5": ["tenue"], "7.0 14.5 34.0": ["kheema"], "8.2 -4.4 3.9": ["inboth"], "-1.7 30.0 6.0": ["besiegement"], "1.1 5.6 13.9": ["microdata"], "9.5 12.7 2.7": ["theman"], "0.1 9.8 12.4": ["dins"], "4.3 -3.1 2.9": ["haitus"], "0.7 13.4 5.9": ["tortuosity"], "15.6 10.9 7.4": ["sunblind"], "14.6 15.1 10.7": ["backscratching"], "17.6 11.5 18.7": ["kolo"], "1.5 5.2 11.4": ["xslt"], "36.2 -4.1 -0.9": ["secondbiggest"], "12.3 4.8 11.6": ["swingarms"], "13.3 15.7 6.3": ["throve"], "22.0 18.6 24.3": ["supercolony"], "4.2 -2.6 6.3": ["kyoon"], "20.2 5.2 0.7": ["bumpf"], "4.7 -3.1 7.7": ["anteed"], "4.7 -1.0 9.0": ["estudiantes"], "5.8 2.8 3.6": ["ystem"], "5.2 9.7 12.0": ["neighbhorhood"], "3.0 2.8 7.0": ["anginal"], "4.8 15.2 10.7": ["restituting"], "12.1 19.6 20.3": ["wariest"], "-7.6 7.0 15.7": ["napaka"], "10.6 8.3 8.4": ["calligraphed"], "0.7 1.0 6.9": ["adulterations"], "5.6 11.6 3.7": ["crookedest"], "-2.9 5.0 -1.4": ["coah"], "8.4 16.0 10.1": ["lievable"], "3.7 -1.0 8.7": ["nutrionist"], "14.6 14.7 12.8": ["bullx"], "23.4 6.3 12.5": ["permantly"], "-0.1 5.6 16.7": ["goan"], "15.0 -5.9 0.1": ["launc"], "10.5 14.3 2.5": ["tostop"], "2.9 8.2 17.6": ["maari", "mabigat"], "18.2 13.2 9.4": ["barristas"], "9.0 3.8 14.1": ["biocomputing"], "16.5 5.9 22.8": ["capuccino"], "24.4 9.4 13.1": ["steelmill"], "4.4 4.5 4.3": ["sanctorum"], "3.2 10.9 5.4": ["greynet"], "12.0 32.7 12.5": ["dauntlessly"], "10.1 13.2 37.2": ["setlines"], "3.3 15.4 -0.9": ["obviosuly"], "8.5 4.9 12.3": ["lod"], "1.5 2.8 6.2": ["decied"], "3.1 2.4 -3.7": ["dualise"], "10.4 9.2 17.4": ["orgins"], "5.7 5.7 14.4": ["trailbike"], "-0.5 4.5 11.2": ["syd"], "10.1 3.5 25.5": ["tonged"], "-0.2 18.9 11.9": ["flowcharting"], "10.8 6.2 11.2": ["cama"], "3.6 6.6 5.6": ["planeside"], "3.3 3.2 7.9": ["coffeeheaven"], "-0.2 14.3 10.4": ["gmae"], "-1.8 -2.7 3.3": ["theschool"], "-3.3 -3.6 6.4": ["quadrivalent"], "-2.9 3.5 15.6": ["siste"], "2.6 -0.8 9.9": ["cerevisiae"], "8.2 5.7 7.9": ["soundworld"], "11.7 5.4 1.6": ["dampered"], "16.3 5.9 11.0": ["roofscape"], "2.0 9.8 12.1": ["jrs"], "0.6 3.8 13.1": ["disablity"], "0.8 12.5 -1.3": ["victorius"], "-0.2 9.5 12.8": ["riparians"], "3.8 18.3 7.9": ["contant"], "0.0 2.8 10.2": ["consisent"], "8.8 13.1 21.9": ["genuses"], "19.6 10.2 15.7": ["backslapped"], "6.1 18.4 9.8": ["interpositioning"], "9.9 5.7 7.1": ["denaturant"], "16.9 25.1 12.4": ["pummelings"], "2.5 -0.8 3.1": ["premies"], "5.8 10.7 11.0": ["defragger"], "17.4 2.5 6.9": ["dollors"], "21.1 12.1 2.6": ["stockpiler"], "5.5 5.9 3.9": ["cameback"], "-1.9 -1.8 8.6": ["oung"], "7.0 24.0 11.0": ["adaptiveness"], "5.6 20.5 14.0": ["sesquipedalian"], "16.8 13.5 12.3": ["cyberland"], "3.4 26.5 13.2": ["wackness"], "6.2 10.2 12.3": ["habba"], "5.8 10.1 1.4": ["radiophone"], "2.5 -0.0 14.3": ["yasmin"], "2.4 15.9 -0.1": ["newsgatherers"], "2.5 13.2 10.0": ["stathead"], "-2.3 10.1 16.9": ["droppage"], "12.0 7.6 5.2": ["mosty"], "10.7 15.6 13.9": ["pronated"], "7.9 8.3 6.8": ["canberra"], "14.4 14.2 14.0": ["notso"], "-3.6 4.4 0.6": ["cadidate"], "6.0 35.2 10.0": ["geostrategically"], "12.9 5.3 35.2": ["unbreaded"], "14.1 3.4 7.2": ["contracter"], "12.2 4.3 4.8": ["crimebusting"], "4.3 -3.0 6.7": ["gemmologist"], "7.0 3.7 6.4": ["interessante"], "-0.7 -0.6 3.4": ["pupillages"], "-4.8 9.0 8.6": ["nonmetropolitan"], "8.0 -0.3 11.8": ["jeroboams"], "12.8 16.3 13.1": ["bumblings"], "2.1 4.8 1.9": ["senti"], "2.7 1.2 13.7": ["monastrell"], "5.5 -4.5 7.5": ["acress"], "2.8 -3.6 5.9": ["medicial"], "9.5 10.7 11.9": ["martime"], "-7.4 20.6 9.8": ["uncuff"], "7.9 -1.5 25.6": ["growout"], "2.7 9.6 10.2": ["hville"], "5.7 8.0 -1.2": ["topromote"], "15.1 15.7 9.0": ["kolkhoz"], "3.7 14.9 11.3": ["danwei"], "-3.3 23.3 0.5": ["inculpate"], "4.4 20.9 9.0": ["naysay"], "17.1 11.6 40.5": ["bryozoan"], "18.0 22.6 8.8": ["teritory"], "13.5 15.4 25.4": ["yuckiness"], "2.6 -3.2 4.1": ["carillonneurs"], "7.0 7.2 3.4": ["polymerizing"], "-2.1 6.2 8.3": ["lesinurad"], "12.1 22.8 12.8": ["hallowing"], "1.5 15.6 12.0": ["cogitations"], "-6.0 3.8 1.4": ["eighteens"], "7.3 14.8 18.4": ["highish"], "13.2 11.6 6.5": ["timelag"], "3.8 14.1 0.3": ["reinvolved"], "11.3 7.0 20.6": ["malecon"], "10.3 15.3 0.7": ["socceroos"], "-6.0 10.8 1.9": ["chemoattractant"], "1.3 9.6 14.5": ["cech"], "-0.6 5.5 12.3": ["administrivia", "hec"], "1.9 13.7 5.9": ["supernote"], "8.5 10.0 21.0": ["platings"], "0.2 14.4 15.7": ["rajya"], "11.7 0.7 23.7": ["groat"], "9.6 4.3 20.5": ["hanga"], "-7.9 5.8 5.1": ["ofsuch"], "4.7 6.2 11.5": ["hillclimbing"], "-0.7 18.7 11.5": ["survial"], "9.4 14.4 11.7": ["tomcatting"], "-6.2 -1.5 8.7": ["scfm"], "6.2 5.3 7.5": ["baum"], "5.8 9.0 3.5": ["earthily"], "9.4 6.2 24.7": ["jetboats"], "4.2 8.1 15.8": ["anumang"], "18.0 23.2 17.5": ["naagin"], "19.2 11.5 27.8": ["coelurosaurs"], "13.9 10.5 12.2": ["unflushed", "buggys"], "7.0 7.2 -6.6": ["prescript"], "-0.9 6.9 11.4": ["standars"], "-4.6 16.2 6.9": ["unarrested"], "20.0 7.8 18.0": ["gibbous"], "8.5 14.7 20.4": ["frizzing"], "7.0 9.6 16.7": ["outfeed"], "11.4 9.7 10.5": ["wikiality"], "-11.0 7.0 4.6": ["tuitioned"], "11.1 10.7 8.1": ["ober"], "6.0 15.4 7.7": ["trackbar"], "3.9 -2.5 9.6": ["oxazepam"], "15.0 3.5 12.2": ["boda"], "0.6 33.2 3.9": ["opponant"], "-3.6 -2.3 4.3": ["amendements"], "2.7 -2.2 4.3": ["gigapascals"], "11.1 39.2 8.8": ["besiegers"], "7.7 17.4 8.7": ["thugging"], "14.9 12.7 9.6": ["aftering"], "16.6 11.2 10.9": ["manbags"], "8.0 2.4 11.9": ["asphaltene"], "11.5 23.7 29.5": ["unwieldily"], "8.0 -2.1 13.8": ["meltabs"], "-10.3 -0.7 9.5": ["subtrochanteric"], "4.3 4.6 9.8": ["piroplasmosis"], "5.4 31.8 19.0": ["inexplicitly"], "4.5 22.1 9.2": ["encounted"], "-2.9 4.0 11.2": ["galvanizers"], "9.7 2.9 9.3": ["depolymerization"], "-1.8 -4.9 5.2": ["livechat"], "7.3 6.0 27.4": ["baingan"], "7.0 -3.0 13.7": ["tappet"], "9.8 -1.6 -0.0": ["supersafe"], "-3.9 5.3 5.8": ["havdalah"], "15.8 4.3 8.6": ["telecharger"], "3.8 10.1 9.3": ["datagram"], "-3.5 -1.3 2.2": ["micropigmentation"], "17.9 9.4 9.6": ["decine"], "6.4 10.0 7.8": ["pingbacks"], "0.1 -5.3 6.7": ["nces"], "4.8 1.4 8.5": ["jugadores"], "5.5 3.1 2.9": ["sweatproof"], "9.3 11.3 21.8": ["schistosome"], "1.7 -3.1 12.4": ["pronouced"], "17.8 18.2 14.5": ["onmy"], "4.3 9.7 9.0": ["tremour"], "6.9 8.6 15.1": ["randall"], "4.6 16.3 7.8": ["problematize"], "6.7 10.5 6.6": ["meridional"], "13.7 8.5 22.7": ["churrascarias"], "-6.0 10.5 19.2": ["tita"], "0.5 -2.4 -1.7": ["newsportal"], "5.2 22.2 12.5": ["plantocracy"], "5.3 8.3 7.1": ["fif"], "10.0 11.5 6.7": ["butched"], "-0.8 13.8 8.4": ["telepromter"], "6.8 10.3 14.4": ["problably"], "9.1 12.7 3.0": ["sustainance"], "8.0 22.7 9.0": ["fanboyish"], "-0.1 -2.8 -0.2": ["deadine"], "-5.2 10.6 3.4": ["antilocks"], "-3.0 1.2 8.9": ["agos"], "6.7 3.4 14.1": ["rhapsodised"], "-0.3 2.9 3.5": ["autotransfusion"], "6.8 23.0 17.0": ["jits"], "5.7 2.2 6.9": ["barcamp"], "4.0 1.7 1.4": ["messieurs"], "6.4 5.0 7.9": ["gentlemens"], "14.1 4.3 16.3": ["vinculin"], "19.8 13.1 24.6": ["bonzai"], "-2.8 6.4 5.3": ["wellrounded"], "-7.0 14.5 2.2": ["congradulate"], "5.4 4.4 6.4": ["drinkdriving"], "6.9 13.5 0.3": ["legaly"], "0.5 2.9 17.2": ["bluesfest"], "7.7 -1.4 -7.0": ["icubic"], "5.4 4.5 9.5": ["icebag"], "-0.3 6.3 6.6": ["abhangs"], "-5.6 5.9 -0.2": ["overcollateralized"], "12.3 12.6 -6.9": ["embassador"], "0.4 13.7 12.6": ["ortiz"], "-0.8 9.6 6.6": ["visibily"], "6.8 4.9 14.4": ["danceathon"], "3.8 23.8 2.1": ["dishonesties"], "-5.7 4.9 -1.5": ["vali"], "12.8 3.6 25.8": ["bhajis"], "5.1 20.0 9.7": ["buddys"], "14.9 3.5 15.5": ["limites"], "21.7 24.3 22.0": ["nards"], "16.6 17.7 -2.5": ["cyberactivists"], "0.5 5.8 6.5": ["connnected"], "6.6 7.7 11.2": ["pinners"], "-1.0 0.7 0.2": ["congener"], "-2.8 3.5 14.8": ["hst"], "1.4 6.7 11.1": ["redsox"], "11.1 7.2 3.9": ["mislabels"], "5.7 5.1 10.5": ["hijos"], "10.3 13.8 10.4": ["coshed"], "20.0 12.1 8.5": ["renationalizing"], "9.3 15.5 3.7": ["oufits"], "1.6 15.0 12.4": ["verrrrry"], "3.4 9.4 15.0": ["recountings"], "12.5 7.2 15.4": ["chimey"], "4.6 10.5 17.0": ["pysched"], "7.3 20.6 4.1": ["antiregime"], "11.3 16.2 8.5": ["contentless"], "5.1 -0.5 5.7": ["sinters"], "0.9 1.8 4.7": ["buse"], "8.1 3.4 2.3": ["seris"], "-6.0 -3.7 -2.7": ["iation"], "4.7 0.9 2.3": ["eastandard"], "-1.7 8.2 5.5": ["unka"], "3.7 3.8 13.3": ["rolfing"], "7.9 12.9 6.7": ["misvalued"], "11.0 -0.7 14.1": ["prewedding"], "8.9 11.7 3.2": ["ignitors"], "-2.2 7.5 5.8": ["onscene"], "-8.2 8.2 1.1": ["disfranchising"], "0.8 3.2 2.4": ["chemosaturation"], "-0.2 2.9 22.5": ["inseason"], "6.6 -0.4 1.3": ["institut"], "11.8 3.2 16.7": ["sut"], "13.5 12.5 -0.2": ["optomism"], "16.2 5.4 9.8": ["programable"], "3.6 -4.1 9.8": ["hih"], "12.7 11.4 8.1": ["mcuh"], "4.7 -0.3 -3.3": ["udenafil"], "6.8 14.7 9.2": ["bureaucratize"], "3.2 14.4 20.6": ["tawk"], "8.7 -1.1 2.9": ["icos"], "15.8 19.7 13.9": ["tiedowns"], "10.0 7.8 14.9": ["chakka"], "8.3 5.6 17.7": ["recontour"], "4.0 8.4 12.1": ["salir"], "6.1 -1.0 10.1": ["inhlawulo"], "0.1 19.6 7.5": ["cemevis"], "5.5 7.8 9.9": ["khanga"], "15.6 9.7 33.7": ["greenfinch"], "4.3 4.7 -1.0": ["avielo"], "9.5 21.2 9.7": ["uncloseted"], "19.5 9.7 37.3": ["linnet"], "10.9 31.0 10.5": ["indiscriminantly"], "15.3 7.1 6.5": ["telenovella"], "8.5 10.0 12.9": ["unaffordably"], "6.6 3.9 8.9": ["decir"], "12.9 10.6 10.8": ["sexxxy"], "-0.4 13.6 9.7": ["iknowtruthismine"], "4.4 13.5 1.1": ["autoscan"], "4.6 0.2 7.6": ["michaels"], "14.9 1.0 7.7": ["macworld"], "14.1 -0.4 3.0": ["doet"], "0.3 17.1 7.6": ["disassociative"], "4.1 7.6 4.7": ["florbetaben"], "10.3 8.8 9.9": ["mcafee"], "1.6 4.9 21.3": ["lifeguarded"], "8.3 -0.2 16.1": ["ject"], "6.8 13.3 15.6": ["bedevilment"], "-6.1 3.6 0.8": ["sistance"], "3.3 21.2 11.9": ["skillwise"], "11.8 6.3 -0.1": ["gamecast"], "4.2 19.1 -2.5": ["adducted"], "14.0 17.9 6.3": ["proplyds"], "3.2 1.0 13.2": ["kyoo"], "1.9 0.6 17.4": ["inni"], "2.0 -0.6 25.4": ["pui"], "4.3 4.7 0.8": ["lawmiss"], "6.5 -0.8 20.5": ["couvert"], "4.2 3.4 21.2": ["lockage"], "4.3 5.6 8.1": ["meaderies"], "11.6 -4.5 10.8": ["microhouse"], "8.9 18.3 13.2": ["drophouses"], "9.4 13.0 8.0": ["stepup"], "5.9 11.9 8.0": ["forestal"], "18.8 6.9 29.1": ["brittlestars"], "0.4 8.1 -0.3": ["stabilizations"], "2.9 17.1 7.3": ["bhool"], "16.5 18.1 15.0": ["fauvism"], "15.9 15.0 21.0": ["handguards"], "13.0 19.1 9.8": ["polictical"], "17.8 17.3 14.8": ["mallrats"], "-3.7 9.0 -5.5": ["allowd"], "24.1 0.9 6.7": ["comanies"], "7.5 25.4 4.0": ["autarchic"], "8.1 15.3 8.8": ["yagu"], "3.8 2.1 4.1": ["clickhere"], "9.4 8.2 19.9": ["nerdily"], "12.9 14.7 15.4": ["pompus"], "2.6 15.0 6.1": ["emendation"], "13.2 -7.4 5.2": ["sheme"], "-0.3 9.0 5.7": ["chemosensitizer"], "1.0 3.9 2.6": ["assignement"], "9.2 30.2 12.3": ["multisectarian"], "3.4 9.5 22.3": ["somet"], "7.2 14.6 5.0": ["physicalize"], "10.3 14.6 12.9": ["boinked"], "6.4 12.1 -4.0": ["documentry"], "-3.8 8.7 7.0": ["unsentenced"], "5.1 2.2 8.8": ["accummulated"], "5.4 -2.2 2.6": ["autoradiography"], "2.7 -1.5 9.8": ["lignocaine"], "13.1 8.2 16.8": ["frug"], "18.7 14.8 19.1": ["todger"], "-1.1 8.0 9.0": ["milner"], "24.6 20.6 13.9": ["pocalypse"], "-2.4 7.6 8.3": ["misyar"], "10.6 8.3 15.9": ["undermount"], "19.4 1.5 12.7": ["economised"], "23.6 8.2 20.2": ["whatchamacallits"], "10.6 11.3 12.5": ["groaningly"], "22.4 3.8 11.5": ["automats"], "1.9 24.9 5.1": ["bullycide"], "4.7 9.7 12.4": ["icked"], "5.5 7.2 10.5": ["wcf"], "9.1 1.9 20.8": ["bunad"], "-1.1 8.9 15.4": ["samajh"], "8.1 -1.8 9.2": ["dinettes"], "8.9 15.6 18.0": ["namby"], "9.7 13.8 -0.1": ["nework"], "5.9 9.4 9.6": ["meller"], "7.6 6.6 14.8": ["megawattage"], "10.3 13.3 9.6": ["officegoers"], "11.3 19.2 26.0": ["peduncle"], "15.7 11.1 7.5": ["bactericides"], "-7.3 0.6 5.5": ["unfractionated"], "5.3 4.7 14.6": ["kalirin"], "6.7 4.0 5.7": ["distrupted"], "3.8 -8.3 1.9": ["sional"], "14.0 9.3 34.6": ["maduros"], "25.3 8.9 23.6": ["zoomorphic"], "14.1 1.6 32.2": ["curtido"], "13.3 11.9 7.6": ["loungerooms"], "10.0 5.6 12.6": ["superbantam"], "11.2 3.6 7.9": ["microgenerators"], "4.6 11.6 8.3": ["nonvascular"], "4.3 3.4 26.2": ["bierocks"], "-0.3 -4.1 -5.5": ["ector"], "10.8 11.8 17.8": ["cleanin"], "10.7 17.6 11.6": ["sleazes"], "12.9 6.9 25.2": ["trug"], "9.9 12.0 7.5": ["washlet"], "14.3 7.7 13.8": ["delayer"], "-6.7 5.6 3.8": ["buildingwide"], "6.4 17.2 3.6": ["arsene"], "3.1 3.8 5.4": ["wioth"], "3.2 17.2 -0.6": ["heuristically"], "6.2 17.7 12.7": ["khukuris"], "5.3 5.0 6.6": ["toolholding"], "-0.3 10.8 4.4": ["taxotere"], "-0.5 4.2 18.2": ["makuha"], "0.0 1.9 8.8": ["ninty"], "6.0 21.2 4.6": ["nikab"], "1.9 -7.7 7.3": ["buhl"], "-8.0 16.5 -0.9": ["eyeopening"], "13.6 18.3 17.2": ["monogamously"], "19.0 21.2 11.6": ["blitzkrieged"], "8.9 13.6 10.9": ["unalarmed"], "11.9 -0.6 16.0": ["yearearlier"], "-5.3 17.8 14.7": ["biopsying"], "12.8 5.1 6.5": ["grupos"], "-6.5 -2.2 2.8": ["teacherage"], "5.3 29.5 12.8": ["goodnik"], "4.2 3.0 8.2": ["kuhn"], "6.2 6.8 13.4": ["rockumentaries"], "13.9 14.2 10.8": ["ingoal"], "5.7 8.9 15.9": ["hemoglobins"], "11.4 24.3 6.2": ["grenaded"], "2.0 29.4 7.7": ["pesh"], "-1.7 28.9 13.1": ["playstyles"], "10.2 7.3 19.0": ["debarker"], "12.7 9.5 10.9": ["pinsetter"], "29.3 5.1 15.1": ["loserboard"], "6.9 -0.8 10.2": ["uncompetitively"], "5.2 3.6 4.4": ["abso"], "14.9 15.7 6.5": ["acquisitors"], "12.6 1.9 24.5": ["fatless"], "16.1 21.0 21.5": ["orishas"], "-5.0 6.0 19.7": ["nonpoint"], "6.9 0.0 -2.3": ["dimisses"], "2.4 15.4 11.3": ["ekklesia"], "14.6 5.4 4.5": ["neckstrap"], "12.0 -5.5 12.0": ["leiu"], "1.2 11.3 4.2": ["tomotherapy"], "1.0 12.7 7.4": ["cadena"], "7.2 12.2 8.2": ["negawatt"], "7.2 11.7 5.2": ["cyberexperts"], "11.5 16.2 6.9": ["electioneers"], "5.3 16.5 5.8": ["dooced"], "3.5 15.1 7.5": ["sidecountry"], "-0.5 4.2 9.6": ["lymphoblasts"], "5.9 2.6 1.0": ["capillarity"], "-5.5 23.6 9.0": ["iffing"], "11.1 26.7 3.9": ["cyberdefenses"], "9.0 11.6 3.1": ["landgrabbing"], "7.7 3.7 11.7": ["imagesetter"], "3.2 2.4 10.4": ["occu"], "10.4 17.5 20.2": ["ristretto"], "14.0 -0.0 4.4": ["accelerographs"], "0.4 25.3 9.1": ["rejecter"], "-4.0 12.1 5.5": ["stagestruck"], "14.6 9.6 36.5": ["cawl"], "10.6 18.3 -2.5": ["atomising"], "2.2 10.7 8.1": ["tamashas"], "18.9 1.9 17.6": ["furbelows"], "13.6 7.9 10.8": ["bbe"], "5.9 1.9 7.9": ["nonlabor"], "1.1 36.3 4.7": ["civlians"], "7.6 6.6 10.2": ["capreomycin"], "1.1 -0.5 10.5": ["taik"], "5.5 20.0 5.4": ["unfrequented"], "3.0 17.4 4.8": ["committedly"], "12.3 12.6 20.3": ["sgraffito"], "7.6 7.7 13.0": ["cyanotypes"], "8.5 -4.9 3.2": ["transer"], "11.9 17.5 6.8": ["picutres"], "5.4 3.2 19.5": ["pulltab"], "16.7 9.9 14.6": ["bodaciously"], "-7.6 -8.7 -4.2": ["representated"], "10.5 2.4 9.6": ["clefs"], "10.7 24.0 10.8": ["pillocks"], "3.1 9.9 7.6": ["deglam"], "2.0 14.1 10.1": ["athletism"], "2.3 8.9 10.0": ["sbin"], "6.6 7.3 7.9": ["vulgarisms"], "3.3 0.9 4.3": ["honolulu"], "24.2 15.0 13.8": ["bogarting"], "5.5 7.5 9.5": ["tournies"], "24.1 2.9 6.3": ["moneyspinners"], "16.9 13.4 11.2": ["naut"], "15.4 4.9 30.9": ["boatsheds"], "5.7 5.8 3.2": ["noida"], "2.5 1.5 6.6": ["registro"], "-6.9 11.5 1.1": ["subinspector"], "16.7 -5.2 7.3": ["intoduced"], "-1.2 -4.1 -0.6": ["productline"], "2.1 19.3 9.8": ["prosperities"], "0.8 -1.4 14.8": ["gamot"], "0.2 18.9 12.0": ["somuch"], "2.9 7.3 23.2": ["baha"], "4.4 5.9 6.5": ["sideshafts"], "20.4 18.5 12.0": ["blagger"], "3.4 22.8 10.4": ["conciously"], "9.2 12.2 50.5": ["megrim"], "-5.1 -5.1 5.0": ["nnual"], "-1.3 6.7 4.1": ["miuntes"], "7.3 6.6 18.3": ["receed"], "-0.6 5.9 11.4": ["luka"], "-3.2 0.8 6.6": ["aradhana"], "1.9 7.8 3.7": ["reprieving"], "2.5 7.6 15.1": ["dimorphism"], "0.6 2.0 11.3": ["kahaan"], "21.3 2.2 36.4": ["presliced"], "2.6 -2.1 10.8": ["chambre"], "10.8 9.0 19.0": ["alecks"], "8.7 9.7 16.9": ["macam"], "6.4 4.9 13.8": ["underlayers"], "1.5 17.7 0.2": ["acknowleging"], "10.4 22.6 10.2": ["miscomprehension"], "9.7 10.1 11.0": ["picolitre"], "10.8 28.2 5.4": ["janissaries"], "12.9 13.7 30.7": ["lungwort"], "11.5 12.1 20.9": ["mathcore"], "11.9 7.4 13.8": ["lightflyweight"], "4.6 10.0 14.3": ["faa"], "16.1 -0.4 21.0": ["laquer"], "-0.8 15.0 8.0": ["schooltime"], "6.8 19.7 4.1": ["aknowledges"], "-5.2 7.2 14.1": ["ovulations"], "4.5 12.6 15.1": ["storie"], "6.0 1.6 23.6": ["malvasia"], "1.0 8.0 -8.0": ["relatio"], "16.5 22.3 31.8": ["bufo"], "4.6 1.6 13.4": ["tongawallahs"], "3.1 0.7 31.3": ["shiro"], "1.8 -3.8 5.8": ["panchakarma"], "6.9 9.8 15.9": ["allantoin"], "2.6 8.1 19.7": ["retting"], "0.1 19.4 2.1": ["swt"], "11.8 10.3 34.5": ["hoecakes"], "6.1 -5.1 8.3": ["ksh"], "0.5 4.9 8.8": ["metatarsalgia"], "18.5 4.9 19.5": ["hairsprayed"], "19.0 -2.2 -2.6": ["companyhas"], "2.3 10.1 15.6": ["showflats"], "7.7 14.9 0.3": ["criticizm"], "5.7 9.3 0.9": ["tral"], "8.2 -6.6 1.0": ["autoplex"], "7.9 9.0 18.7": ["speleothems"], "-2.4 15.2 12.8": ["microdissected"], "2.3 12.3 20.7": ["kamo"], "12.8 16.8 12.8": ["evacuators"], "6.6 -0.3 10.8": ["nent"], "17.8 23.0 11.9": ["louses"], "-0.9 0.1 -4.4": ["explaines"], "7.8 19.4 3.3": ["behin"], "-2.6 9.1 -7.1": ["suppot"], "0.0 12.5 11.2": ["thim"], "0.5 6.8 2.8": ["artherosclerosis"], "-2.2 13.4 -2.5": ["rolapitant"], "4.8 1.9 7.9": ["exportability"], "11.3 2.1 10.1": ["upaid"], "-0.8 22.9 -2.4": ["assiduousness"], "5.1 10.1 2.6": ["jumpseat"], "16.9 18.2 47.3": ["hellgrammites"], "9.9 15.8 16.5": ["overtightened"], "-2.7 16.9 6.2": ["whichwould"], "12.1 5.1 8.2": ["spaza"], "-2.1 17.8 6.8": ["dharam"], "-6.6 11.6 7.6": ["plice"], "13.3 -1.8 7.7": ["palletiser"], "1.4 8.6 11.2": ["myc"], "1.4 8.6 5.1": ["upd"], "5.4 9.7 10.5": ["cronic"], "8.3 12.7 4.3": ["mzee"], "16.8 10.2 22.4": ["swamper"], "0.2 4.6 3.1": ["bracketry"], "11.3 10.3 19.8": ["weldable"], "3.9 4.0 20.8": ["sharecropped"], "-0.5 3.6 4.8": ["elocutionist"], "-1.7 14.9 11.3": ["constructionists"], "1.4 -0.2 7.1": ["tob"], "-6.8 3.8 11.0": ["rebuffering"], "18.0 -3.5 14.8": ["sackbut"], "7.5 5.4 25.1": ["rubrum"], "5.5 -1.3 9.3": ["lignes"], "1.4 2.4 7.8": ["injectivity"], "11.0 11.9 17.0": ["hyperstylized"], "24.1 8.1 19.7": ["cartonnage"], "17.8 3.2 9.4": ["chemcials"], "8.8 -0.7 7.0": ["antispasmodics"], "-3.9 8.0 2.9": ["dualing"], "1.6 12.0 2.9": ["thefact"], "9.2 6.4 22.2": ["sweetpotato"], "11.0 -7.6 14.5": ["rollings"], "3.5 18.5 13.2": ["pheran"], "16.6 22.8 20.8": ["pooka"], "5.5 4.5 -4.1": ["beneifts"], "1.9 -1.8 1.3": ["unamortised"], "17.1 17.9 18.0": ["pusses"], "-2.4 2.5 0.3": ["pago"], "-0.9 0.5 -1.3": ["theavailability"], "6.0 -1.0 8.7": ["gennaio"], "-7.6 6.9 13.5": ["fellowshipped"], "10.3 14.3 1.7": ["firers"], "-1.2 -3.8 12.2": ["unsupplemented"], "4.3 -0.2 8.9": ["graingrowers"], "5.1 20.5 2.2": ["sensationalization"], "-1.1 6.1 11.1": ["skatepunk"], "-1.9 -7.5 1.4": ["dicas"], "-7.2 9.8 -13.7": ["canditate"], "11.9 4.2 13.9": ["nagara"], "7.0 8.4 7.4": ["misdialing"], "4.0 8.4 14.5": ["shapefile"], "13.0 9.1 9.9": ["hussled"], "31.7 10.1 25.6": ["eggbeaters"], "8.9 8.1 5.4": ["mordern"], "-1.1 9.1 14.5": ["kampanya"], "0.6 -2.9 -0.3": ["sofia"], "6.2 17.1 3.7": ["explictly"], "2.0 8.3 -0.2": ["oppos"], "12.0 10.2 11.9": ["swooper"], "4.3 6.9 2.4": ["cytopenia"], "19.6 8.8 24.0": ["heds"], "7.9 12.7 13.3": ["mjh", "illions"], "4.6 9.9 21.1": ["esculenta"], "3.6 22.8 8.2": ["judaization"], "-6.9 2.1 11.1": ["osteoinductive"], "14.0 12.7 13.9": ["lysostaphin"], "5.9 11.7 11.8": ["rima"], "3.5 19.6 11.1": ["vihara"], "5.1 9.8 16.8": ["papule"], "17.0 12.8 26.7": ["albus"], "-6.9 -2.9 3.0": ["reserch"], "7.4 4.0 23.7": ["spaghettis"], "12.4 11.8 28.9": ["chapulines"], "9.9 20.7 8.6": ["reequipping"], "0.6 -0.4 6.2": ["sinonasal"], "0.9 11.5 3.5": ["dissappoint"], "11.0 10.4 24.5": ["tequilla"], "5.5 8.3 4.1": ["vasodilating"], "-0.2 8.4 9.3": ["mailo"], "11.5 8.6 9.0": ["winkling"], "9.4 17.0 16.8": ["strimming"], "9.5 12.0 11.7": ["properous"], "20.3 9.4 15.5": ["rubicund"], "1.3 11.7 17.7": ["calll"], "4.3 -0.6 5.6": ["neurotherapeutics"], "6.5 -1.4 5.9": ["invesments"], "19.4 -2.1 -5.6": ["launchs"], "7.9 17.2 12.3": ["chhote"], "7.3 7.0 6.9": ["ecamsule"], "5.9 9.5 19.6": ["herbaceousness"], "8.9 10.4 11.2": ["restaining"], "18.2 18.1 8.6": ["likejacking"], "14.6 33.3 18.0": ["superbeing"], "-0.6 -0.8 1.4": ["zoledronate"], "1.9 23.6 15.6": ["submissives"], "0.8 7.8 10.0": ["businessplace"], "8.8 6.4 18.0": ["backcomb"], "-1.9 7.4 4.2": ["unan"], "4.4 23.8 6.6": ["uncasing"], "19.5 12.7 9.8": ["morter"], "17.3 9.2 28.2": ["breadless"], "5.7 12.9 16.7": ["tnx"], "8.5 19.7 14.8": ["jeeze"], "7.7 9.9 1.5": ["recompensing"], "10.6 -1.7 21.5": ["nirmalya"], "10.0 -1.9 4.1": ["rephasing"], "-6.5 -4.7 -0.1": ["ctions"], "11.2 20.2 9.1": ["necrophiliacs"], "10.0 12.3 7.3": ["phrenologist"], "2.2 16.3 10.7": ["khaas"], "-1.6 -0.8 2.6": ["pseb"], "6.2 9.3 19.7": ["statsheet"], "3.3 6.5 0.1": ["hopsitals"], "14.7 19.7 1.3": ["hullabaloos"], "-1.4 6.3 -1.2": ["grandaunts"], "10.3 20.9 6.5": ["disprovable"], "11.6 9.3 15.2": ["bloggery"], "8.4 -5.4 7.1": ["jik"], "8.6 13.4 13.8": ["abcesses"], "4.2 6.9 11.9": ["gyri"], "2.0 9.5 5.3": ["baliff"], "-4.8 6.7 16.2": ["regifters"], "-3.0 25.9 14.4": ["uprightly"], "13.0 6.3 10.2": ["voil"], "12.5 7.1 9.3": ["zelf"], "-4.1 8.0 4.5": ["relationshp"], "3.9 13.8 10.2": ["shelovesmodernwhomp"], "10.0 16.9 11.5": ["taximan"], "8.0 27.7 2.2": ["undestroyed"], "8.6 13.3 16.5": ["duece"], "10.5 10.8 12.4": ["epithelioid"], "3.2 28.5 17.2": ["simunition"], "-2.2 24.5 0.7": ["madrasses"], "8.9 1.7 12.4": ["nonskiers"], "2.3 4.6 16.5": ["methampethamine"], "5.2 21.0 9.2": ["interventionary"], "-6.4 5.4 8.2": ["lized"], "18.9 3.6 15.1": ["daylighted"], "9.7 6.0 16.9": ["jambo"], "8.1 -1.5 -0.3": ["tns"], "-3.9 -1.3 3.9": ["reverify"], "8.6 5.3 4.3": ["inher"], "3.7 13.0 7.1": ["overmanaged"], "5.8 9.4 19.4": ["flowway"], "8.0 10.9 23.4": ["serration"], "-7.0 -4.1 4.4": ["metrostyle"], "15.0 11.5 11.7": ["arestill"], "3.9 18.3 14.4": ["sublethal"], "2.5 4.6 10.9": ["sido"], "13.4 7.4 15.4": ["tektites"], "13.7 3.5 11.5": ["giddha"], "-0.9 12.7 6.9": ["onc"], "16.1 -1.8 5.3": ["overpayed"], "6.0 4.3 13.0": ["rockcrawling"], "14.1 13.6 22.9": ["borzoi"], "6.7 5.2 3.0": ["engrossment"], "-0.3 26.7 -2.7": ["instrumentalised"], "-0.3 2.9 -1.9": ["trackmen"], "4.3 7.2 15.3": ["disse"], "10.6 15.7 12.0": ["gipper"], "9.2 6.6 -0.3": ["philantropist"], "11.2 17.7 3.3": ["pushiest"], "5.6 12.2 1.4": ["reac"], "11.4 17.2 20.3": ["booboisie"], "12.1 5.7 12.5": ["effervescing"], "4.5 15.9 5.8": ["bahaviour"], "10.1 1.0 2.6": ["polysulfide"], "12.8 5.5 -4.5": ["underpressure"], "2.6 19.6 0.6": ["polisario"], "19.3 7.1 9.9": ["insto"], "8.7 20.2 9.7": ["truckling"], "-1.2 10.4 1.6": ["posssession"], "7.2 2.3 -3.7": ["bigpharma"], "7.9 4.2 24.2": ["tinga"], "8.0 1.6 4.2": ["commssion"], "6.3 3.6 4.4": ["vinay"], "3.9 21.2 5.7": ["voicelessness"], "11.4 4.5 31.9": ["houseboaters"], "10.3 16.8 8.0": ["flickable"], "1.9 6.9 9.0": ["multihop"], "8.1 23.3 12.8": ["marchin"], "0.3 22.3 -6.7": ["delegitimised"], "11.3 3.6 9.8": ["torchieres"], "-2.3 1.0 6.2": ["brach"], "14.6 14.8 12.3": ["qwest"], "18.7 29.0 8.8": ["killswitch"], "17.5 11.1 14.1": ["xeon"], "1.6 -6.7 3.7": ["gamme"], "3.3 -6.5 -3.6": ["decidedto"], "15.3 3.6 7.6": ["faciliated"], "10.6 19.2 20.9": ["caugh"], "9.8 7.3 0.8": ["organziations"], "15.5 0.4 -3.6": ["hardselling"], "23.8 16.1 14.9": ["geektastic"], "13.4 11.5 12.9": ["megaregion"], "-7.4 5.2 7.4": ["gamewinners"], "10.7 7.7 7.8": ["conjurors"], "5.2 5.9 29.2": ["arrabiata"], "-0.1 15.3 4.4": ["organiation"], "-2.6 5.6 7.4": ["relocators"], "5.0 2.6 3.5": ["underdrain"], "6.0 9.3 5.2": ["videorecording"], "3.6 24.1 12.0": ["stalin"], "0.9 8.2 -0.8": ["crtical"], "11.0 5.6 2.5": ["sertaneja"], "5.7 17.5 9.8": ["autodiscovery"], "8.6 9.9 0.1": ["commitmentto"], "6.7 1.4 6.2": ["minuter"], "4.2 16.0 10.7": ["tourettes"], "-0.6 10.7 7.8": ["fitr"], "7.8 13.1 12.0": ["hunkiness"], "8.5 6.0 29.7": ["matsuri"], "15.4 7.0 19.9": ["ktla"], "6.4 18.9 0.7": ["propulsively"], "-1.7 8.4 27.8": ["runnier"], "8.4 5.0 12.1": ["tijd"], "-3.7 14.9 12.4": ["faulters"], "-5.6 -5.9 11.4": ["noncounty"], "3.7 9.2 18.2": ["laisse"], "17.5 13.3 26.0": ["dabber"], "3.1 0.5 9.7": ["eeting"], "22.8 12.4 30.2": ["racquetballs"], "-5.8 15.8 8.2": ["subjectiveness"], "16.1 8.0 30.6": ["lacecap"], "12.4 -2.8 2.4": ["setted"], "18.5 21.3 10.4": ["dispiritedly"], "16.4 6.0 16.6": ["moonboot"], "0.7 12.3 -1.0": ["nect"], "11.2 7.7 25.2": ["handbuilding"], "4.3 3.9 12.1": ["planimetric"], "14.2 21.9 9.3": ["repukes"], "8.7 5.0 8.6": ["schwannomas"], "4.9 8.3 -3.5": ["alledges"], "0.1 -5.4 10.4": ["ministerials"], "9.9 10.8 22.7": ["katoey"], "-2.6 12.0 6.0": ["presidentials"], "-0.6 9.7 10.4": ["trialhorse"], "-2.0 10.8 8.2": ["eigenen"], "-2.3 25.1 8.1": ["ideologized"], "6.0 -7.1 14.5": ["postconsumer"], "6.8 8.4 1.9": ["colonography"], "6.5 3.1 19.9": ["sanga"], "4.6 0.5 4.0": ["grabaseat"], "9.1 21.5 13.1": ["dooo"], "-0.6 26.8 -3.8": ["terro"], "18.1 24.7 10.7": ["redials"], "-0.4 18.0 1.6": ["enoughto"], "3.1 4.5 33.5": ["nihari"], "2.1 9.3 8.8": ["raingardens"], "7.2 3.0 5.9": ["srt"], "1.3 6.9 2.9": ["buspar"], "-2.3 9.2 1.5": ["audiometric"], "13.7 11.3 10.0": ["respiring"], "12.9 18.3 5.7": ["parsec"], "9.1 14.9 18.0": ["earthiest"], "0.6 4.5 3.6": ["pected"], "0.2 -0.4 5.7": ["thodi"], "17.3 23.5 11.7": ["clodhopper"], "1.2 8.2 -1.1": ["solubilizing"], "5.7 6.6 18.1": ["kapaskhali"], "19.6 32.5 4.2": ["enslaver"], "8.2 2.0 6.7": ["suplus"], "5.0 5.2 4.6": ["warfooting"], "9.9 11.8 8.5": ["novicey"], "-0.9 2.2 18.7": ["auana"], "3.4 -2.7 14.5": ["juku"], "3.0 16.1 12.2": ["inaptly"], "11.8 10.2 2.3": ["enouraging"], "4.8 14.4 13.7": ["ianlou"], "6.2 13.1 3.7": ["unmounting"], "20.5 -5.7 3.6": ["compny"], "1.4 10.0 9.7": ["bullspread"], "-5.6 -3.9 4.3": ["retransplantation"], "-0.6 -3.9 4.5": ["ciclopirox"], "23.3 10.5 20.7": ["pulverizers"], "10.7 15.3 7.0": ["tawdrier"], "15.9 14.4 21.8": ["crotching"], "-8.9 6.4 19.8": ["hardnesses"], "2.7 9.7 1.5": ["wehre"], "6.8 8.6 20.8": ["catchbasins"], "3.5 8.5 9.7": ["dolomitized"], "11.3 18.4 9.0": ["irrepairable"], "-2.6 14.7 7.6": ["synergist"], "17.1 7.7 21.0": ["spitless"], "1.9 4.2 -0.5": ["ipc"], "1.4 9.6 11.7": ["sabo"], "-8.6 -2.2 5.5": ["invalidations"], "11.1 12.0 20.7": ["itsy"], "9.4 12.3 12.9": ["declensions"], "18.4 8.8 37.6": ["avacado"], "1.4 7.1 6.3": ["prestandard"], "15.8 19.3 3.1": ["indigenize"], "-10.5 -4.1 6.5": ["lities"], "10.2 15.2 6.8": ["whoremonger"], "0.2 4.6 10.5": ["rre"], "5.6 29.4 16.6": ["shotgunner"], "1.5 -1.9 -0.1": ["speculatory"], "3.5 8.1 10.4": ["fornia"], "12.2 5.9 21.3": ["cottonwool"], "-4.8 3.5 7.2": ["assi"], "10.4 20.0 9.2": ["boasters"], "-1.1 9.1 4.2": ["nondecision"], "7.9 29.2 -0.2": ["outscheme"], "14.4 20.5 15.7": ["lockpick"], "6.9 5.4 1.5": ["directement"], "10.3 7.6 14.7": ["plastisol"], "10.6 -0.3 3.0": ["lactide"], "-2.2 4.3 -5.6": ["expl"], "1.4 14.0 2.1": ["exchangeables"], "10.4 8.6 12.9": ["smellin"], "10.2 0.1 10.2": ["sewerline"], "1.9 8.1 8.7": ["basesloaded"], "11.1 14.9 12.3": ["exacty"], "12.4 12.9 10.2": ["firees"], "5.1 6.0 15.6": ["heterogeneities"], "5.7 2.2 25.8": ["sinsemilla"], "-2.3 27.6 7.8": ["gangmembers"], "9.1 7.4 32.7": ["vegatables"], "8.0 17.2 11.4": ["carlisle"], "2.9 6.6 4.5": ["freetime"], "7.3 -6.3 -0.3": ["atory"], "-0.2 14.7 8.9": ["perameters"], "-1.5 7.1 8.9": ["quaresma"], "12.8 29.5 16.9": ["goodniks"], "1.3 0.5 -3.1": ["toother"], "-7.0 4.2 -2.2": ["blawg"], "6.3 9.6 8.4": ["explicably"], "10.4 13.7 14.2": ["overfertilize"], "-10.1 1.1 2.4": ["extemp"], "8.4 10.4 9.4": ["southeastwards"], "-2.1 -2.1 2.7": ["sysops"], "-0.4 6.4 8.0": ["frontotemporal"], "24.3 26.1 15.7": ["wookiee"], "3.2 23.4 7.1": ["unworthily"], "1.4 4.1 13.9": ["kilobase"], "3.9 12.3 12.8": ["echoic"], "-10.4 4.5 -0.9": ["perioperatively"], "8.8 9.4 4.4": ["orthopedically"], "4.0 20.1 -5.2": ["pogram"], "13.4 14.1 10.4": ["paparrazzi"], "14.3 2.8 8.3": ["phosphide"], "5.8 20.1 9.2": ["shittiness"], "5.8 16.2 13.3": ["mayne"], "6.4 15.3 18.4": ["toxocariasis"], "7.8 1.9 8.2": ["tudes"], "-2.4 18.9 7.2": ["mortifications"], "5.2 5.0 -0.4": ["cybertheft"], "14.5 8.7 12.2": ["ornateness"], "24.0 28.4 21.4": ["batlike"], "-0.6 -7.7 6.9": ["exten"], "2.5 8.7 2.0": ["shuout"], "-6.5 7.4 3.6": ["siyum"], "-2.0 -1.9 13.6": ["amie"], "-3.3 3.2 -1.8": ["ctive"], "0.8 -3.9 6.9": ["expen"], "13.1 8.8 7.9": ["bizjets"], "3.8 11.3 -1.7": ["ioniser"], "-4.6 16.5 10.3": ["bouting"], "7.9 9.4 13.6": ["reticulum"], "1.0 -7.3 9.3": ["lempiras"], "9.0 10.4 30.9": ["honeycreepers"], "2.2 6.0 14.6": ["garimpos"], "21.9 13.2 19.5": ["indolently"], "-5.1 7.9 -3.2": ["reccurrence"], "7.5 22.4 11.5": ["desperations"], "-3.1 20.3 5.1": ["parapsychological"], "14.1 -0.2 6.7": ["purcahse"], "8.1 8.1 11.5": ["tarah"], "19.3 10.0 5.3": ["embarressed"], "14.3 4.3 13.9": ["snazzily"], "1.7 4.3 16.6": ["epiphyseal"], "14.1 13.7 13.7": ["rubbering"], "19.6 11.7 8.5": ["cosmopolis"], "13.6 10.5 25.0": ["gaurs"], "6.0 15.3 2.5": ["converstation"], "12.6 12.0 5.3": ["backpeddled"], "20.4 5.6 28.2": ["monopile"], "9.8 -0.9 16.2": ["flameworking"], "24.7 10.7 27.6": ["redgum"], "3.3 22.7 7.9": ["rageaholic"], "14.6 -3.4 33.9": ["frita"], "3.9 11.9 6.4": ["secondteam"], "17.0 7.4 26.4": ["horseshow"], "8.2 23.8 16.2": ["backchecks"], "-0.2 8.8 6.7": ["everyweek"], "4.5 -2.6 3.2": ["hydroelectrical"], "3.2 4.4 -1.8": ["atg"], "9.0 18.0 15.0": ["jamarat"], "4.5 8.1 18.8": ["quinellas"], "4.7 13.0 6.3": ["censoriousness"], "2.4 10.3 11.8": ["ossicles"], "1.2 8.6 14.6": ["ayan"], "14.8 17.3 29.1": ["defeathering"], "1.0 -2.4 8.5": ["erbyn"], "14.6 18.4 5.0": ["faliure"], "12.1 22.7 13.6": ["elsewheres"], "10.8 9.1 15.4": ["patulin"], "-1.0 2.5 2.7": ["nidhi"], "26.5 13.0 33.2": ["coypu"], "5.6 4.6 -0.0": ["curcuit"], "3.9 4.0 3.5": ["inancial"], "12.2 18.8 6.6": ["centralists"], "4.7 10.6 -1.4": ["jiziya"], "8.1 23.1 5.7": ["unlosable"], "-2.1 3.3 0.4": ["columist"], "2.5 14.0 6.8": ["microcavities"], "13.4 16.2 12.0": ["bodyparts"], "8.9 20.7 27.8": ["melaleucas"], "0.4 -3.6 6.9": ["ofn"], "3.0 15.7 14.1": ["methyltransferases"], "16.1 8.4 12.1": ["doob"], "-2.3 1.6 1.0": ["collateralizes"], "15.0 10.8 18.3": ["geolocator"], "11.6 -4.4 5.4": ["teamwear"], "0.1 17.7 -1.2": ["artha"], "-0.9 7.5 2.0": ["berman"], "16.8 20.0 18.8": ["wolfmanshowlforever"], "4.0 2.6 6.2": ["dge"], "2.0 -2.7 -0.7": ["femoropopliteal"], "7.1 -0.3 2.5": ["catherization"], "16.6 4.7 2.0": ["laserjet"], "-4.2 11.9 10.2": ["ruralness"], "20.3 9.7 29.6": ["flowerlike"], "2.7 10.0 7.5": ["tropy"], "3.2 10.3 10.8": ["resorb"], "14.2 17.7 9.4": ["twistedly"], "12.7 12.8 9.6": ["ramrods"], "5.7 -1.2 16.0": ["chiao"], "11.4 17.7 28.0": ["overhunted"], "9.8 7.1 7.6": ["toreturn"], "11.3 9.6 26.6": ["dracaenas"], "1.6 22.4 -2.4": ["missionizing"], "13.3 6.5 12.7": ["bodydrop"], "17.7 15.8 17.3": ["wangs"], "16.2 15.1 23.3": ["plimsoll"], "4.6 9.7 7.1": ["silencio"], "10.0 22.2 15.7": ["mindnumbing"], "8.4 8.5 18.9": ["nyika"], "3.1 18.0 14.6": ["climatized"], "-6.3 -5.0 12.6": ["reccomends"], "7.8 5.7 -10.2": ["aletter"], "7.1 19.1 7.2": ["litigative"], "3.5 2.4 13.6": ["makapag"], "18.1 9.3 43.1": ["barby"], "7.8 8.7 17.9": ["uplisted"], "5.4 7.2 12.7": ["inge"], "22.6 7.4 30.6": ["choccie"], "13.1 -3.1 12.8": ["rockfest"], "16.4 5.6 22.4": ["frangipanis"], "4.9 19.7 15.3": ["snoozefests"], "4.8 8.6 -0.7": ["believethat"], "3.9 1.4 15.0": ["iddi"], "2.9 1.1 34.8": ["bavette"], "0.7 2.2 11.6": ["jejunal"], "17.4 12.8 14.9": ["campery"], "8.7 9.2 18.7": ["amare"], "15.4 8.3 7.5": ["showcourts"], "13.2 -5.6 35.9": ["smokery"], "0.9 8.1 0.3": ["admittted"], "2.2 7.4 -3.6": ["historics"], "13.4 10.6 16.2": ["countesses"], "3.5 8.7 12.1": ["depilated"], "8.3 2.4 11.7": ["dding"], "1.4 16.5 3.7": ["werekilled"], "8.9 5.2 15.0": ["highspot"], "2.7 25.2 5.6": ["viler"], "5.9 13.4 20.4": ["casketed"], "8.0 6.9 18.5": ["wisk"], "3.3 16.1 7.9": ["oposite"], "3.8 24.7 0.3": ["yids"], "19.2 2.6 9.4": ["readymix"], "9.1 15.0 15.9": ["paci"], "13.2 4.8 3.9": ["redubbing"], "30.7 14.6 15.6": ["godzilla"], "6.4 -0.5 3.2": ["progamming"], "0.9 -2.2 7.4": ["etouches"], "8.9 14.3 24.6": ["mordida"], "-1.0 -5.2 2.9": ["moreinformation"], "11.6 4.1 13.4": ["yp"], "5.9 0.6 14.9": ["neptune"], "-8.6 2.4 -5.0": ["yaers"], "19.6 -13.3 15.6": ["recylcing"], "-3.9 1.4 10.1": ["peti"], "-0.7 -0.5 2.7": ["oxazolidinone"], "-8.5 8.8 2.4": ["condomise"], "8.1 4.2 13.3": ["lavalier"], "3.6 16.8 6.4": ["hapening"], "-8.3 10.4 5.1": ["prioritizations"], "8.4 9.9 14.1": ["kulintang"], "17.6 12.5 22.2": ["lagomorphs"], "15.7 16.5 26.6": ["smeller"], "-6.3 3.8 1.6": ["derate"], "10.4 4.2 8.9": ["disapppointing"], "8.5 20.2 21.5": ["fringers"], "-3.9 5.3 17.6": ["pumasok"], "10.6 20.6 9.6": ["disperser"], "5.3 3.9 9.8": ["subgingival"], "1.0 15.8 1.6": ["considred"], "1.8 16.3 9.9": ["tely"], "14.1 -6.8 -1.6": ["sponored"], "16.4 3.8 30.4": ["huarache"], "5.2 11.2 -5.3": ["scrutiniser"], "7.7 12.6 5.1": ["tunately"], "3.7 -0.8 9.6": ["masectomy"], "7.7 6.6 0.4": ["zidane"], "13.2 11.6 26.0": ["chickies"], "3.7 11.6 20.2": ["eventide"], "11.7 10.0 7.0": ["tinnier"], "15.4 -4.2 13.7": ["fixups"], "11.3 14.1 15.0": ["loanwords"], "11.5 1.0 16.1": ["dota"], "11.4 14.2 24.8": ["drupe"], "10.7 25.3 2.7": ["icasualties"], "8.3 15.5 8.2": ["multiplicities"], "0.2 7.6 2.5": ["dualized"], "14.2 20.2 6.4": ["restfully"], "5.8 16.1 12.6": ["decontaminations"], "19.3 8.2 11.6": ["manfacturers"], "5.8 6.1 8.7": ["repeg"], "7.1 20.4 15.1": ["conspecific"], "6.4 17.0 6.1": ["ibori"], "-10.0 5.2 10.5": ["fincom"], "10.8 14.7 15.0": ["forebearer"], "8.2 5.9 17.7": ["zzzzzzz"], "6.2 31.2 11.1": ["enfeebles"], "12.7 7.4 6.4": ["popul"], "19.6 18.1 19.7": ["subaqueous"], "12.0 22.5 23.6": ["gloomer"], "5.0 20.4 6.6": ["disinhibiting"], "11.9 9.8 31.3": ["jalfrezi"], "30.2 18.0 33.9": ["waterbugs"], "7.5 6.9 7.1": ["desite"], "14.5 3.9 1.9": ["neuroengineering"], "18.2 1.7 30.0": ["mayhaw"], "13.5 11.4 12.3": ["jodphurs"], "19.4 10.3 18.8": ["hairclip"], "-1.1 0.1 -4.0": ["concertized"], "4.1 33.7 5.3": ["gaddafi"], "12.7 10.0 1.8": ["jubliant"], "9.6 -1.2 11.3": ["salida"], "5.3 10.5 15.3": ["trouncings"], "-7.9 16.3 -3.5": ["greivances"], "9.3 -18.7 -11.2": ["adr"], "9.6 12.1 16.5": ["factorization"], "-3.0 -0.6 2.0": ["attendace"], "11.4 8.1 30.5": ["paprikash"], "9.2 2.9 7.2": ["circumaural"], "11.1 14.9 10.5": ["vidic"], "-6.6 -0.5 7.8": ["travaux"], "-5.5 2.9 4.8": ["fns"], "2.3 13.1 6.6": ["anammox"], "8.3 21.5 16.2": ["enactors"], "12.5 -0.9 21.3": ["springwater"], "2.2 10.3 7.2": ["parthenolide"], "4.6 13.9 11.3": ["acident"], "0.6 0.4 8.7": ["laparascopic"], "2.0 9.5 10.3": ["punchiness"], "4.9 3.8 1.5": ["inaugration"], "10.0 6.1 21.8": ["allday"], "16.5 6.3 34.4": ["beamy"], "13.1 16.6 17.8": ["parches"], "3.5 2.7 4.0": ["develpoment"], "10.8 14.6 13.4": ["megaevent"], "-2.6 2.5 -0.2": ["investiga"], "18.0 -2.5 6.9": ["milliondollar"], "25.6 12.3 29.5": ["gunnera"], "-4.3 12.1 1.0": ["misapprehends"], "9.0 2.1 -2.3": ["midfelder"], "14.6 7.0 15.4": ["kiswa"], "1.4 7.4 1.6": ["foreignexchange"], "3.8 -3.5 15.8": ["chah"], "0.9 15.4 0.8": ["servere"], "5.5 6.9 8.0": ["convento"], "8.8 2.6 10.1": ["complexe"], "7.6 7.4 12.3": ["votos"], "9.0 24.6 7.1": ["hornswoggle"], "4.0 3.0 -6.3": ["yestrday"], "12.9 1.6 14.6": ["coventry"], "10.6 16.5 7.4": ["unmerry"], "7.5 19.3 8.5": ["orgasming"], "11.0 9.0 36.2": ["hawksbills"], "9.5 10.1 12.2": ["trolleyed"], "19.5 14.9 24.5": ["eucalyptuses"], "2.8 3.9 9.1": ["headsup"], "3.7 16.4 18.4": ["kempo"], "5.1 3.5 11.7": ["fuertes"], "11.1 -8.6 6.6": ["rejuvination"], "9.3 -0.1 -3.3": ["knownas"], "2.9 6.2 15.6": ["salita"], "10.0 10.5 0.4": ["tornament"], "-5.7 1.3 -5.9": ["generale"], "6.4 6.0 -0.5": ["voivodships"], "6.0 9.5 36.4": ["dotterel"], "7.9 14.1 10.1": ["lysing"], "10.1 10.7 15.4": ["himalayan"], "-0.5 10.6 0.8": ["suceeding"], "3.1 -2.0 12.4": ["ddau"], "5.3 -2.4 2.3": ["anouncing"], "19.5 22.8 16.5": ["cobbers"], "6.6 6.4 12.1": ["undersaturated"], "-4.3 -0.7 -1.9": ["neurobehavioural"], "6.7 14.3 12.9": ["outragious"], "-6.3 9.5 12.1": ["stephens"], "5.2 25.0 21.0": ["recurves"], "22.6 12.4 24.7": ["fortis"], "-2.3 -3.3 1.8": ["quez"], "3.8 17.1 5.8": ["preety"], "17.3 16.5 26.0": ["cankerous"], "4.4 12.2 4.0": ["aerodynamical"], "12.4 11.8 13.7": ["akon"], "4.0 3.5 8.6": ["manges"], "-2.4 1.9 13.4": ["foodsafety"], "16.0 7.9 22.0": ["asphault"], "2.7 5.6 15.3": ["lamar"], "8.4 6.3 16.6": ["hooptie"], "15.3 9.5 17.6": ["bonza"], "9.9 10.4 -0.8": ["trumpcard"], "11.4 10.6 5.8": ["antiheroic"], "10.7 17.2 -0.3": ["othes"], "3.1 11.7 11.1": ["arp"], "7.8 5.8 15.4": ["pyrope"], "4.5 24.5 -5.0": ["voluntarist"], "5.0 8.7 8.8": ["biliterate"], "12.9 8.5 8.3": ["wakefield"], "-2.1 2.9 10.5": ["labioplasty"], "9.6 8.8 9.0": ["photochromics"], "18.8 9.1 26.5": ["panela"], "1.9 19.2 13.7": ["sexlessness"], "21.0 2.5 14.0": ["calliopes"], "1.1 3.8 13.3": ["burnoffs"], "1.8 1.2 11.2": ["ikely"], "2.1 3.1 16.1": ["bigla"], "6.8 -4.3 10.3": ["polychloroprene"], "19.7 9.2 37.8": ["mousies"], "-3.5 6.1 13.4": ["gabe"], "3.8 31.6 2.8": ["unilaterals"], "-5.3 4.1 4.3": ["apd"], "18.9 9.3 35.1": ["rattail"], "-3.7 8.5 8.7": ["osteosarcomas"], "11.1 12.1 3.0": ["jetters"], "1.3 2.5 12.9": ["fsu"], "2.8 4.9 5.8": ["derechos"], "14.1 5.8 27.5": ["mauby"], "-3.1 -2.7 -4.7": ["eyars"], "6.5 13.8 4.3": ["sexaholics"], "24.5 10.1 11.4": ["disintegrator"], "16.6 14.3 15.4": ["automarket"], "12.7 8.5 19.8": ["snacktime"], "26.8 12.5 14.4": ["riproaring"], "-2.0 10.2 -3.3": ["laudation"], "3.3 6.2 16.5": ["bandi"], "-1.5 11.6 9.6": ["sundalo"], "21.8 15.6 22.1": ["cawed"], "13.4 10.3 5.4": ["boilovers"], "19.3 12.8 12.8": ["proprietarily"], "14.4 16.8 14.9": ["schwa"], "7.3 -0.6 47.2": ["seabream"], "7.2 9.3 3.3": ["caravansary"], "3.3 4.2 31.5": ["buah"], "4.2 0.9 11.2": ["vareity"], "3.6 26.2 0.6": ["profanes"], "7.6 -5.9 7.2": ["caberet"], "2.5 -4.4 -3.8": ["addresed"], "8.1 17.6 12.5": ["inveigles"], "-0.0 7.6 7.5": ["dalton"], "0.1 -7.7 3.9": ["veen"], "10.7 17.3 17.5": ["diddums"], "7.3 11.4 20.1": ["nuffin"], "11.6 25.1 16.7": ["outbattle"], "11.1 16.0 7.6": ["deflater"], "0.1 3.7 19.6": ["acoustica"], "5.5 3.2 5.6": ["recontextualization"], "5.6 -0.4 10.2": ["bpsd"], "2.8 2.6 11.5": ["manera"], "8.2 11.2 13.9": ["carribean"], "6.7 7.9 3.2": ["ideographic"], "9.6 12.5 5.5": ["hokiest"], "0.8 -1.9 12.1": ["gies"], "3.7 11.0 11.3": ["fulton", "bomberos"], "-4.6 8.6 11.2": ["publice"], "-7.8 19.4 -3.9": ["vitiation"], "-1.6 19.1 1.7": ["grievences"], "2.5 0.6 -1.4": ["theproduction"], "23.0 9.0 11.1": ["subisidies"], "6.5 13.3 10.4": ["ranieri"], "7.2 14.2 5.0": ["himsel"], "1.8 -5.4 -1.5": ["labo"], "4.0 24.9 13.6": ["thinketh"], "-0.1 17.0 2.3": ["pressence"], "19.7 5.8 15.5": ["petchems"], "10.9 5.9 8.0": ["wekeend"], "12.6 4.1 12.7": ["mycorrhiza"], "18.7 11.3 11.6": ["guying"], "0.7 18.6 3.3": ["rumsfeld"], "14.5 15.8 24.1": ["whin"], "10.8 17.1 10.1": ["incredibilistic"], "3.4 13.9 17.4": ["desu"], "2.5 12.1 7.6": ["wsdl"], "1.4 11.7 19.2": ["toughy"], "10.1 11.3 19.6": ["ephemerally"], "3.0 8.0 -2.3": ["benefitial"], "7.3 3.2 8.6": ["philippine"], "-12.7 -2.3 -0.5": ["recodified"], "13.6 14.2 14.1": ["mmkay"], "13.9 12.6 22.9": ["garrigue"], "29.6 9.9 22.1": ["dribbly"], "13.8 -3.4 6.9": ["perfo"], "9.2 -2.7 9.4": ["priceof"], "10.6 17.7 12.1": ["unornamented"], "6.8 -0.6 -0.4": ["dispells"], "7.3 7.0 10.1": ["jenn"], "11.0 10.1 9.9": ["sticken"], "14.1 8.0 9.1": ["mensen"], "3.8 9.9 13.7": ["toteswinger"], "6.0 10.2 8.4": ["sids"], "18.5 11.5 17.6": ["silverish"], "11.1 15.0 9.7": ["channelrhodopsin"], "5.9 8.3 3.0": ["roosevelt"], "5.1 11.0 4.7": ["vidwans"], "4.9 6.7 15.2": ["firn"], "12.4 4.7 17.4": ["amba"], "18.8 9.5 14.3": ["buggie"], "14.2 10.1 21.8": ["cowslip"], "16.4 10.9 10.5": ["stang"], "0.6 7.3 11.6": ["keri"], "15.4 17.7 15.9": ["prokaryote"], "-3.0 11.3 12.2": ["seminomas"], "14.1 9.3 16.7": ["kickballs"], "10.1 16.6 9.3": ["shakingly"], "2.6 1.3 21.4": ["lagan"], "4.3 -7.5 8.1": ["nonbaseball"], "18.2 1.2 12.2": ["ferrocene"], "10.2 2.5 9.1": ["vient"], "10.1 25.4 7.0": ["fingerpoint"], "17.2 14.8 8.1": ["bajar"], "1.7 20.0 5.1": ["veiws"], "6.0 10.4 12.9": ["paideia"], "-0.4 5.7 3.4": ["confirmative"], "1.4 0.9 1.2": ["readaptation"], "16.4 1.7 11.5": ["axled"], "2.4 0.4 8.5": ["uniformally"], "9.4 6.8 8.4": ["buenas"], "16.5 11.1 5.4": ["cameraless"], "11.3 14.1 16.1": ["weezy"], "-6.5 0.5 0.8": ["edcuation"], "-3.5 -2.6 -2.3": ["cytric"], "6.7 1.6 2.9": ["rge"], "9.1 11.3 8.4": ["californium"], "4.9 -1.1 8.5": ["subsetting"], "4.3 6.0 -2.2": ["supportes"], "0.1 12.4 10.5": ["aapne"], "13.6 24.1 3.4": ["aparatus"], "12.1 8.7 16.5": ["gauzily"], "2.6 12.7 9.4": ["palpability"], "7.1 20.2 7.5": ["geist"], "9.2 5.8 5.8": ["nonthermal"], "9.8 4.4 28.3": ["gianduja"], "18.0 5.5 8.8": ["liquefication"], "8.5 10.1 5.0": ["employeers"], "5.5 5.5 8.8": ["multipass"], "10.7 6.7 8.6": ["barres"], "-5.0 12.8 -7.4": ["negotiatior"], "9.7 11.8 9.1": ["thecoming"], "8.1 2.7 3.6": ["unrecouped"], "-0.1 1.3 6.6": ["clinc"], "7.4 5.5 8.9": ["atteint"], "8.8 19.8 9.5": ["pertinacious"], "16.1 6.7 12.2": ["faddists"], "11.6 7.3 14.5": ["visaholders"], "16.1 2.2 16.5": ["celing"], "11.3 13.0 12.9": ["anoying"], "7.5 14.7 13.6": ["kachcha"], "0.5 -5.3 6.0": ["tahun"], "12.4 -2.4 3.8": ["servizi"], "6.0 18.4 19.0": ["underwatering"], "5.6 13.2 11.2": ["scrutinies"], "1.9 2.2 7.8": ["lesional"], "9.4 4.9 5.8": ["thoseexpressed"], "8.4 -2.6 -5.5": ["aprivate"], "12.1 -6.5 5.6": ["thesale"], "22.3 19.0 13.1": ["retrorockets"], "6.4 13.6 7.9": ["metaphysicians"], "7.5 17.1 5.1": ["conops"], "12.0 13.0 14.5": ["unwatchably"], "5.3 6.8 -1.5": ["foreigh"], "7.0 5.1 10.8": ["buenos"], "5.8 8.9 13.1": ["collagenous"], "3.9 5.3 23.4": ["bowrider"], "-2.7 24.2 12.3": ["prescriptively"], "14.2 15.2 4.0": ["holographically"], "2.4 25.7 17.0": ["outquick"], "19.3 14.2 32.4": ["hibiscuses"], "1.4 11.9 10.4": ["lookingfor"], "5.2 3.1 14.9": ["shodeo"], "1.6 -2.4 11.8": ["nonemployer"], "9.9 23.0 24.2": ["budworms"], "10.1 12.2 21.0": ["lunglessness"], "6.0 8.4 -0.4": ["demonstratable"], "14.7 5.9 5.9": ["aughties"], "2.5 0.5 1.3": ["functionalizing"], "11.7 5.3 12.5": ["adjacently"], "10.7 9.3 15.2": ["ricked"], "0.7 -0.7 8.1": ["chehk"], "11.4 10.4 15.9": ["appaloosas"], "8.1 1.6 7.8": ["saddlecloths"], "-7.0 11.8 6.9": ["resonse"], "-0.7 3.0 6.3": ["upmixing"], "6.7 3.3 21.0": ["probinsya"], "5.2 18.3 11.6": ["mke"], "2.5 3.7 12.2": ["oms"], "8.7 2.2 2.1": ["venued"], "10.4 13.9 7.4": ["overstimulates"], "0.4 0.6 7.7": ["prostratin"], "3.0 -0.2 3.5": ["babystyle"], "9.3 2.6 8.3": ["desposit"], "11.6 19.5 25.0": ["scrawniest"], "10.4 7.9 3.1": ["identifiying"], "10.3 -1.0 -0.8": ["ookie"], "16.4 25.2 13.1": ["hussars"], "2.0 16.4 0.4": ["accumen"], "19.7 7.8 12.5": ["oilcos"], "12.4 9.9 19.4": ["boles"], "11.3 8.1 2.1": ["tensegrity"], "1.8 13.5 11.7": ["nonsurgically"], "4.9 3.9 8.6": ["midlifers"], "-1.9 3.8 0.2": ["anthological"], "10.0 12.2 6.2": ["cacheing"], "2.7 14.4 7.3": ["neurally"], "8.6 20.0 5.1": ["minimalise"], "9.8 15.0 47.4": ["spurdog"], "5.1 1.7 11.4": ["mannies"], "6.6 9.2 2.5": ["zeigen"], "25.8 16.8 8.3": ["screeen"], "14.4 1.8 2.8": ["nonbroadcast"], "-0.2 8.6 12.0": ["dut"], "12.6 8.3 26.5": ["coontie"], "3.2 -6.2 3.5": ["micromorph"], "14.4 -0.0 7.7": ["goldplated"], "3.9 19.8 5.3": ["srael"], "7.6 3.0 7.7": ["ventouse"], "6.9 11.2 5.6": ["serioulsy"], "8.9 13.4 11.5": ["rahm"], "6.8 2.7 11.6": ["oeil"], "19.0 5.5 25.2": ["cagoules"], "11.5 15.3 14.8": ["madhouses"], "10.9 5.5 6.3": ["clic"], "3.7 10.4 9.4": ["murali"], "9.3 20.5 5.3": ["cruely"], "1.1 1.9 -4.1": ["fourm"], "-1.6 7.2 2.8": ["warrantable"], "3.8 2.5 5.3": ["soonafter"], "-3.8 11.2 5.0": ["wheeldrive"], "5.0 6.8 4.0": ["decompiler"], "4.6 2.7 1.5": ["electrocoagulation"], "14.3 20.2 15.3": ["wooooo"], "-5.5 -0.1 5.3": ["nephrotoxic"], "4.8 23.2 18.1": ["dopeness"], "7.1 7.1 13.2": ["kuryente"], "4.9 17.8 14.0": ["overpursuit"], "-5.4 4.1 2.7": ["attainted"], "12.5 9.9 25.2": ["woodruff"], "10.0 -0.2 4.2": ["resite"], "15.7 14.4 16.8": ["manc"], "-0.5 -0.8 11.9": ["fering"], "1.5 6.4 -1.4": ["apricitabine"], "9.1 -0.4 -6.8": ["gmm"], "9.1 13.3 11.2": ["gadi"], "1.0 4.2 6.3": ["ounds"], "4.0 8.9 18.8": ["microplastics"], "10.5 14.2 5.2": ["aerosolised"], "2.5 12.8 29.6": ["jetskiers"], "11.0 5.1 11.5": ["epix"], "-6.0 8.7 10.3": ["adriano"], "-1.0 -2.2 4.3": ["continuting"], "4.6 7.5 11.6": ["physiochemical"], "16.3 11.9 10.9": ["botom"], "3.5 7.7 3.4": ["fuori"], "2.1 0.9 8.2": ["nonrepresented"], "8.5 10.7 3.6": ["midlander"], "13.6 20.2 17.8": ["distempered"], "-1.4 -6.6 11.3": ["rockland"], "1.7 28.0 30.0": ["brontispa"], "8.9 5.4 13.6": ["lento"], "9.6 7.0 4.5": ["inpact"], "12.0 25.9 8.0": ["emotionlessly"], "8.3 19.2 12.3": ["dbag"], "11.9 7.6 23.2": ["pastelitos"], "-3.9 8.4 3.4": ["rifamycins"], "2.4 9.4 -1.5": ["inititiative"], "10.4 12.0 16.1": ["grmce"], "20.1 18.9 22.8": ["fukin"], "8.0 2.2 9.2": ["siendo"], "1.9 19.2 8.5": ["starvations"], "12.5 2.5 46.0": ["goujons"], "6.9 0.3 6.2": ["settop"], "19.6 4.0 4.1": ["utlities"], "3.5 16.4 17.5": ["landfalling"], "2.0 6.0 -3.1": ["longserving"], "2.1 -0.4 0.7": ["cnd"], "11.5 20.2 4.9": ["threatscape"], "16.1 1.2 20.8": ["ferneries"], "17.4 15.7 9.1": ["flamewars"], "-3.9 2.6 2.8": ["tiapamil"], "-8.2 16.5 -2.0": ["particularised"], "-4.3 7.6 1.0": ["enantioselective"], "3.1 3.0 6.6": ["olopatadine"], "7.6 1.0 8.6": ["mixshow"], "15.5 13.4 19.1": ["dobs"], "1.0 1.1 2.5": ["foresaid"], "12.3 8.7 16.6": ["quadra"], "6.9 18.6 6.2": ["ignominies"], "6.8 4.4 4.5": ["emeafinance"], "6.8 8.3 12.7": ["agriproducts"], "-7.7 2.7 1.8": ["nonservice"], "-1.0 8.9 3.7": ["megadisasters"], "6.9 2.7 8.3": ["minimoto"], "3.1 2.8 -4.6": ["unreceived"], "3.7 -0.1 4.8": ["queremos"], "8.2 18.5 13.5": ["sloooow"], "0.0 16.6 -3.0": ["doubtable"], "8.1 15.6 2.2": ["blaringly"], "-2.0 11.8 -0.6": ["micrometastasis"], "2.0 5.9 6.3": ["inmigrantes"], "5.8 -0.9 -0.9": ["islikely"], "-1.6 -1.5 15.1": ["hdb"], "6.4 13.4 5.6": ["necrology"], "17.2 7.5 1.3": ["sambaed"], "-5.5 5.6 8.4": ["meetthe"], "1.3 12.8 8.3": ["fluctations"], "15.8 14.9 17.0": ["bracings"], "5.6 22.9 8.4": ["elusion"], "8.6 1.2 10.4": ["sonoluminescence"], "-2.2 0.1 -4.0": ["retu"], "-5.1 11.2 2.1": ["metion"], "9.0 4.1 13.0": ["spitzer"], "7.0 10.4 27.7": ["lutea"], "3.9 7.1 9.9": ["filtrations"], "10.3 13.9 10.9": ["kemosabe"], "-6.4 10.0 12.5": ["catechumen"], "2.7 5.7 10.9": ["subrack"], "-3.3 2.0 7.3": ["blawgs"], "14.4 -4.5 -1.2": ["islocated"], "12.0 8.8 6.8": ["kpop"], "3.0 9.1 9.6": ["consitutes"], "10.0 7.5 14.5": ["scapulars"], "7.1 16.4 20.4": ["teenagehood"], "6.1 0.5 18.0": ["barcos"], "8.7 9.6 12.8": ["czardas"], "-3.1 5.1 26.2": ["mirch"], "13.9 12.2 7.3": ["hostler"], "6.5 15.0 13.1": ["outquicked"], "19.0 13.1 25.5": ["untanned"], "1.7 -5.0 -2.8": ["discusssions"], "16.7 8.2 14.1": ["untucking"], "-0.6 6.0 10.9": ["naku"], "5.0 12.9 9.5": ["floodproofing"], "3.3 11.4 3.2": ["indigenising"], "-6.7 16.6 3.2": ["netsh"], "15.8 1.9 23.3": ["pomander"], "14.3 23.0 5.2": ["unchoreographed"], "-3.3 -4.0 -6.1": ["anulled"], "9.5 12.6 6.3": ["interactiveness"], "15.4 5.3 15.7": ["postrock"], "12.9 4.2 12.9": ["uts"], "4.3 36.3 4.8": ["woyane"], "5.9 21.9 1.9": ["becasuse"], "-1.2 9.1 9.9": ["voluntourists"], "12.4 20.2 9.3": ["jovian"], "6.2 2.8 6.5": ["computerizes"], "-3.6 2.4 -1.8": ["fresman"], "15.0 13.2 11.1": ["ophile"], "-2.1 5.4 4.1": ["interet"], "-0.0 3.4 12.2": ["varchar"], "6.3 11.1 15.3": ["trimwork"], "6.8 3.7 13.3": ["thens"], "9.8 9.7 8.2": ["spelet"], "12.7 4.1 48.2": ["mojarra"], "7.3 5.6 9.1": ["wanabees"], "16.9 19.9 17.8": ["bicycler"], "6.2 7.0 10.2": ["maintaince"], "12.5 15.9 15.3": ["saturnalia"], "15.9 18.4 20.8": ["monkies"], "16.0 26.2 26.5": ["deerflies"], "17.0 1.2 30.8": ["guanabana"], "23.5 -0.4 4.7": ["invester"], "10.1 21.3 12.1": ["twittery"], "12.5 10.3 17.4": ["ahaha"], "4.3 11.9 1.3": ["backgroud"], "5.8 -1.2 18.7": ["schneider"], "25.8 1.3 15.5": ["stripmall"], "3.0 5.5 15.3": ["lifestlye"], "3.7 -0.1 2.1": ["accured"], "2.9 -1.3 8.0": ["micropumps"], "-0.1 6.8 16.9": ["moldmakers"], "0.6 5.9 9.1": ["impacton"], "12.9 6.6 3.1": ["blueyonder"], "10.6 2.3 6.1": ["vidcasts"], "19.6 7.8 33.1": ["souffl"], "9.2 6.6 4.6": ["geon"], "2.2 -3.4 4.9": ["quinacrine"], "7.4 16.3 13.8": ["disapoint"], "13.5 4.3 24.2": ["riced"], "6.7 9.3 10.3": ["hysteroscope"], "11.5 8.4 5.5": ["verkauft"], "-0.5 7.0 1.6": ["trotz"], "16.9 15.4 25.3": ["viridian"], "5.2 1.2 11.3": ["municipalites"], "11.4 3.8 29.2": ["landrace"], "17.4 12.5 5.8": ["golpe"], "1.4 14.7 16.2": ["tipuna"], "8.8 20.1 38.3": ["fisherperson"], "13.3 11.2 13.8": ["claques"], "13.7 20.3 4.3": ["unoriginally"], "10.9 16.2 30.6": ["tanoak"], "3.3 22.9 17.8": ["fath"], "12.0 10.0 25.4": ["bellbird"], "9.0 22.3 11.9": ["curtness"], "13.7 9.8 27.6": ["anticuchos"], "-2.1 12.8 11.0": ["biphosphonates"], "25.0 26.3 29.6": ["lubber"], "37.2 8.7 -5.9": ["conglomorate"], "15.3 18.5 22.0": ["diablos"], "8.6 4.5 13.0": ["caprine"], "6.7 7.6 16.7": ["lactalbumin"], "18.6 16.0 10.0": ["icide"], "4.7 14.3 6.6": ["robocallers"], "25.5 7.9 27.5": ["neko"], "12.7 -1.7 6.5": ["theoriginal"], "11.2 3.9 13.6": ["ovariectomized"], "15.2 3.7 8.6": ["myfoxboston"], "14.0 -5.5 12.1": ["riverview"], "9.5 17.2 10.1": ["mughal"], "5.4 6.8 9.6": ["pyraclostrobin"], "7.0 12.4 25.1": ["mabuhay"], "7.9 6.8 16.0": ["rba"], "-7.2 3.1 11.1": ["kesh"], "-1.7 -0.8 6.4": ["radioimmunoassay"], "7.0 -1.2 -0.6": ["deltatre"], "-6.5 15.3 -1.2": ["convinience"], "0.5 4.5 8.8": ["metrobus"], "13.1 22.5 13.1": ["unphotogenic"], "6.2 11.5 13.8": ["salut"], "22.0 31.9 20.1": ["winepress"], "7.5 -0.8 1.9": ["sublicensee"], "-4.6 2.7 3.7": ["hasidic"], "1.9 21.2 13.7": ["panicing"], "-4.6 6.6 1.5": ["nucleolar"], "7.8 9.3 7.5": ["recuts"], "15.0 1.3 26.0": ["dogbane"], "7.3 3.3 20.0": ["tohu"], "-0.8 13.0 3.9": ["ritiro"], "9.9 25.9 4.2": ["latifundios"], "9.7 15.3 6.6": ["adumbrate"], "7.1 4.7 8.0": ["alking"], "-5.1 -8.5 -8.0": ["direcor"], "0.6 11.9 10.0": ["talak"], "8.3 14.7 14.8": ["colonizations", "boatsmen"], "5.6 38.2 2.6": ["miitary"], "5.2 8.2 10.4": ["lactones"], "10.0 6.0 11.8": ["rooflight"], "15.4 -3.5 10.5": ["totebags"], "6.7 16.1 1.6": ["bystanding"], "17.1 -3.0 -1.1": ["lanceert"], "1.1 -0.9 13.0": ["dropin"], "11.8 14.6 6.8": ["cerate"], "5.2 -4.2 6.3": ["pectoralis"], "8.4 19.6 9.8": ["presentism"], "11.5 0.7 -2.7": ["wesite"], "4.2 9.6 5.0": ["findet"], "8.7 4.8 13.3": ["monzodiorite"], "0.4 11.7 0.7": ["appeares"], "8.9 10.8 16.1": ["misbehavin"], "5.2 13.8 13.7": ["nightriders"], "5.5 20.1 7.8": ["ramify"], "7.6 0.8 6.0": ["chared"], "26.8 4.2 16.8": ["gigante"], "16.2 17.5 21.0": ["fxcarden"], "18.8 12.7 20.6": ["funbags"], "6.2 5.3 10.7": ["nanolayers"], "17.5 10.5 17.8": ["wiffle"], "3.1 11.4 7.2": ["thatthis"], "0.6 1.1 3.0": ["salesof"], "-4.2 7.0 3.5": ["revascularizations"], "11.0 1.5 26.8": ["palominos"], "14.3 4.7 26.6": ["striation"], "11.4 3.3 18.7": ["hotsprings"], "3.2 11.0 0.9": ["yuva"], "7.3 7.7 14.2": ["mesophilic"], "7.6 7.2 4.7": ["propio"], "4.9 -4.8 12.6": ["electroless"], "15.0 10.5 15.7": ["abstractionism"], "2.7 12.1 2.4": ["garantee"], "-7.6 10.1 -1.6": ["antitorture"], "17.5 4.4 36.8": ["pastichio"], "10.4 5.5 12.4": ["treaments"], "-6.0 4.2 12.5": ["nandito"], "14.6 -3.6 -0.2": ["fourstar"], "5.8 5.7 13.2": ["nueve"], "10.7 23.4 8.8": ["skycam"], "6.0 19.9 14.9": ["henpecking"], "18.6 6.9 3.8": ["wpd"], "17.5 3.3 20.2": ["hobnail"], "-2.7 0.8 15.2": ["taxables"], "16.7 17.9 7.1": ["whiplashing"], "12.0 19.0 9.7": ["passsengers"], "5.1 10.0 7.2": ["queercore"], "5.9 2.6 9.4": ["catechol"], "5.3 12.2 13.5": ["makeshifts"], "8.1 4.3 27.2": ["bouchons"], "-2.2 14.0 -8.4": ["eader"], "11.7 -0.4 19.9": ["herringbones"], "-0.9 0.3 6.9": ["rencontre"], "6.9 9.0 33.5": ["babirusa"], "7.1 11.1 8.3": ["dabka"], "4.7 5.3 9.8": ["chahe"], "8.2 9.5 15.0": ["theback"], "1.2 18.3 14.9": ["wdm"], "11.9 10.0 9.1": ["fetchmail"], "23.4 11.4 30.8": ["paperbark"], "12.2 3.5 9.1": ["entero"], "-10.3 -7.5 5.2": ["parathyroidectomy"], "1.9 -0.5 1.9": ["agancy"], "12.7 16.0 11.8": ["flippable"], "18.0 11.3 11.8": ["ambitionless"], "2.6 4.9 17.5": ["tohunga"], "0.7 4.5 15.7": ["worht"], "7.5 22.1 7.8": ["bastardizes"], "13.0 13.3 19.9": ["pasttimes"], "15.0 6.9 15.8": ["milkbar"], "15.2 15.2 17.1": ["waterlog"], "5.2 -3.2 -1.9": ["volve"], "1.9 12.8 16.4": ["scunnered"], "6.0 4.9 -1.7": ["aesthetica"], "12.2 39.2 13.2": ["satans"], "5.0 -0.1 9.1": ["shopgirls"], "7.3 1.3 23.4": ["fallling"], "9.1 5.7 2.4": ["denar"], "5.6 -1.5 0.6": ["subsribers"], "13.5 23.4 16.8": ["atomosphere"], "15.0 2.9 52.4": ["rockcod"], "12.5 22.7 11.8": ["botting"], "3.4 7.3 2.8": ["pretensioner"], "10.1 7.5 36.5": ["turtlehead"], "-0.8 -4.2 5.2": ["disucss"], "6.6 7.1 16.6": ["americanos"], "10.9 8.0 11.7": ["hunderd"], "-3.5 2.9 -0.7": ["clevidipine"], "22.6 20.3 12.7": ["repellers"], "7.1 14.5 7.5": ["subline"], "14.4 19.3 18.3": ["qdots"], "24.6 5.4 22.1": ["croco"], "10.6 -2.1 13.0": ["cynnig"], "4.2 -1.6 10.9": ["atthis"], "8.2 11.6 12.5": ["territorians"], "5.0 5.2 8.8": ["dilatoriness"], "7.7 0.0 2.2": ["carisbamate"], "25.4 10.7 47.3": ["moonfish"], "16.1 13.6 23.8": ["footholes"], "3.1 12.5 10.8": ["stdint"], "-5.6 9.3 4.6": ["hemorrhoidectomy"], "0.1 3.0 6.1": ["blanketeers"], "5.5 12.8 11.9": ["stereotypies"], "0.8 10.5 13.8": ["skil"], "5.9 10.2 -3.1": ["unteach"], "-2.0 5.9 14.6": ["palmitoyl"], "15.5 10.9 26.2": ["eggcup"], "6.9 10.2 16.6": ["seema"], "5.3 -1.1 6.1": ["galerie"], "2.1 19.5 11.2": ["nonwar"], "13.4 9.3 2.3": ["analysists"], "14.6 21.7 10.5": ["remants"], "3.8 3.6 25.0": ["desalted"], "13.6 -1.8 11.1": ["informazioni"], "6.1 13.3 12.5": ["fingermarks"], "20.1 21.3 14.5": ["apparitional"], "16.8 11.8 10.4": ["braniacs"], "11.1 8.9 5.1": ["macroenvironment"], "9.6 8.1 7.6": ["resonably"], "7.4 15.0 28.7": ["bati"], "3.0 7.0 14.6": ["poomse"], "8.0 12.1 20.5": ["breton"], "3.0 13.0 11.9": ["pahadi"], "8.2 7.7 11.2": ["natur"], "4.7 12.1 4.5": ["zion"], "7.1 1.0 4.5": ["wakala"], "11.3 -8.4 -9.0": ["agreementwith"], "5.8 24.4 12.6": ["becareful"], "6.4 0.7 15.6": ["eclogite"], "9.3 3.1 10.9": ["polyacetal"], "-1.8 15.9 8.6": ["noncampaign"], "9.4 7.7 27.4": ["tuataras"], "7.0 6.6 36.2": ["kambing"], "3.6 32.3 2.1": ["balkanise"], "9.7 7.2 11.0": ["microbalance"], "5.8 3.1 0.8": ["tyle"], "15.1 -7.5 9.2": ["blowmolding"], "7.4 20.2 15.1": ["funnin"], "1.9 4.0 13.9": ["blant"], "2.2 0.9 10.1": ["melsanthi"], "11.5 16.1 2.7": ["prophesizes"], "-5.8 11.6 -1.1": ["iqbal"], "7.0 9.1 4.7": ["superkids"], "-4.8 4.9 4.9": ["scholly"], "1.6 10.3 -0.6": ["impingements"], "12.1 13.0 22.5": ["podocarpus"], "2.7 11.7 15.0": ["tracebacks"], "6.5 5.8 14.5": ["hasps"], "-1.3 -4.1 -5.8": ["videoconferenced"], "1.7 16.6 7.9": ["fansub"], "11.3 -2.6 29.1": ["assiette"], "-0.6 11.9 9.6": ["deliverances"], "14.7 11.9 30.2": ["plumaged"], "15.1 26.1 12.7": ["badland"], "17.2 2.8 11.1": ["startingly"], "18.5 3.0 2.4": ["titl"], "-2.8 9.0 12.5": ["ironwomen"], "1.4 10.8 3.0": ["specfically"], "9.1 -3.4 6.7": ["kibbitzing"], "1.2 9.8 14.6": ["choe"], "-6.6 13.3 6.1": ["anwers"], "8.5 16.7 15.9": ["hornlike"], "6.0 23.1 8.1": ["moveon"], "6.3 9.6 13.2": ["motho"], "4.5 20.1 13.6": ["idealizations"], "7.3 15.5 13.2": ["miserablism"], "-8.5 -0.7 8.1": ["spondylolysis"], "15.9 17.8 3.9": ["easybeat"], "21.1 5.4 34.2": ["delicata"], "8.2 9.2 15.3": ["saari"], "5.9 1.8 23.0": ["noho"], "-0.7 17.8 10.2": ["backtests"], "-6.5 15.5 5.2": ["fairminded"], "12.0 19.0 21.7": ["pidgeon"], "-5.8 -4.2 6.4": ["esl"], "1.5 14.7 7.8": ["contiune"], "-3.1 38.4 9.0": ["muj"], "15.5 26.7 8.8": ["enterprize"], "7.5 5.2 8.6": ["pumpset"], "14.3 18.4 17.6": ["chachalaca"], "-0.0 7.1 9.3": ["sexercise"], "14.5 20.2 10.9": ["evar"], "4.3 3.7 -3.6": ["toenhance"], "3.4 16.6 4.6": ["vexatiously"], "17.1 5.7 15.5": ["rimshots"], "7.0 2.1 1.7": ["vodcasting"], "-6.2 15.6 -3.2": ["imortant"], "3.3 12.8 13.3": ["filarial"], "8.9 20.7 1.0": ["hoaxster"], "5.4 10.2 3.1": ["bluejacked"], "21.4 3.7 4.3": ["zeleznice"], "8.7 12.0 21.4": ["aftertastes"], "13.1 13.4 20.6": ["crepey"], "19.3 19.7 15.1": ["razorwire"], "-0.1 2.7 10.2": ["clavicular"], "-2.2 22.7 11.3": ["megafires"], "5.3 12.4 8.5": ["homoeopaths"], "17.7 12.2 25.4": ["dextral"], "7.1 9.0 20.3": ["nshima"], "7.2 13.8 8.7": ["nanofilms"], "-8.2 21.5 4.9": ["wartimes"], "21.3 -0.3 6.3": ["ultrahip"], "4.4 14.2 15.1": ["backwashed"], "0.9 18.0 2.6": ["mohajirs"], "8.0 5.8 4.9": ["einigen"], "1.9 20.8 0.2": ["disingenious"], "10.6 22.5 6.4": ["schemings"], "12.4 26.8 12.8": ["plebians"], "11.9 6.1 26.1": ["placecards"], "-2.1 5.6 2.6": ["glucocorticosteroids"], "-3.3 7.3 -1.7": ["cem"], "-5.6 11.4 -3.3": ["derogates"], "13.1 -6.3 9.5": ["bsmt"], "9.7 17.1 18.8": ["krauts"], "7.4 16.8 17.0": ["nonromantic"], "-6.8 -2.9 4.6": ["reenrolled"], "9.5 -8.6 8.9": ["todayto"], "21.9 13.4 15.1": ["mutilator"], "10.9 4.0 5.0": ["suprime"], "10.5 20.3 12.1": ["pedaler"], "1.5 20.8 7.3": ["nonracist"], "13.3 10.6 -0.4": ["cybernauts"], "17.0 2.3 40.9": ["gravadlax"], "12.8 4.4 12.7": ["chocolaterie"], "-1.8 18.9 4.4": ["premediated"], "24.3 12.7 21.7": ["shillelaghs"], "16.0 8.7 37.8": ["roquette"], "18.6 3.8 -4.9": ["topselling"], "4.8 12.1 7.6": ["unrequired"], "13.6 -11.4 4.4": ["sextupled"], "2.0 3.2 7.2": ["soutbound"], "-8.3 -1.9 2.2": ["uel"], "8.6 8.0 8.9": ["adquate"], "8.0 10.3 2.8": ["mistranslating"], "3.1 7.3 12.5": ["kerr"], "3.4 30.9 5.2": ["disuniting"], "-2.3 -3.0 -2.4": ["isat"], "12.8 11.8 36.2": ["thimbleberry"], "-3.6 17.3 1.5": ["mistahs"], "-2.7 1.9 2.7": ["inco"], "3.8 4.4 8.3": ["bulid"], "1.4 -0.0 -2.6": ["superscout"], "-1.0 9.5 5.8": ["wallacea"], "8.0 -2.0 0.4": ["distcoms"], "17.2 12.0 1.2": ["forray"], "19.3 -0.6 11.5": ["epxected"], "7.0 15.5 7.0": ["pleiotropy"], "7.3 12.9 15.3": ["seering"], "8.3 4.5 3.3": ["dunia"], "6.5 15.2 16.5": ["microtrends"], "16.3 15.3 6.8": ["pfennig"], "11.5 8.4 9.4": ["inadequates"], "4.9 -6.5 6.5": ["reattributed"], "9.7 19.8 0.4": ["demostrators"], "4.7 -9.2 -6.7": ["enews"], "12.5 8.7 12.8": ["bustout"], "1.8 4.9 11.6": ["conceptus"], "-2.3 9.8 0.2": ["aof"], "8.0 -7.0 5.4": ["provde"], "-2.5 9.1 1.4": ["engager"], "7.3 1.0 10.2": ["blueseventy"], "24.4 3.7 -8.1": ["superhub"], "20.7 9.6 17.5": ["chaffs"], "-0.4 3.5 2.7": ["emerson"], "10.4 11.5 15.1": ["snowplowed"], "-3.6 8.2 7.3": ["theosophical"], "16.9 13.5 13.0": ["adrenalised"], "10.4 8.0 1.3": ["enamour"], "8.2 9.8 19.0": ["onequarter"], "9.1 2.6 -2.9": ["municipalize"], "6.3 4.8 9.0": ["mehrere"], "0.4 17.2 11.4": ["baazi"], "-2.1 -3.5 -7.5": ["vcfo"], "12.2 11.0 26.1": ["stampeders"], "1.1 -1.3 3.7": ["desealing"], "22.3 3.3 10.8": ["clickety"], "3.2 21.1 11.0": ["skillshot"], "1.7 18.0 5.0": ["rematching"], "10.3 11.7 7.8": ["freestylin"], "2.2 10.7 6.6": ["prority"], "8.0 19.9 16.1": ["farter"], "8.2 0.4 15.4": ["facili"], "-3.6 -0.8 -0.3": ["precollegiate"], "13.1 14.8 12.8": ["whallop"], "3.4 4.4 0.9": ["bosman"], "5.6 18.0 7.5": ["jumpshooter"], "5.7 6.2 4.3": ["ensur"], "10.7 7.6 4.8": ["punchup"], "3.8 2.1 0.4": ["mce"], "9.7 21.8 26.5": ["krait"], "14.9 12.4 9.4": ["rewoven"], "7.2 5.2 11.1": ["peur"], "3.4 20.3 8.6": ["ibhunu"], "10.3 -3.4 4.4": ["weekand"], "20.8 13.7 21.3": ["parrotheads"], "25.0 18.5 25.3": ["piata"], "13.0 18.7 15.7": ["antidisestablishmentarianism"], "19.7 9.1 5.7": ["biofueled"], "5.7 5.2 6.8": ["sublessee"], "8.3 17.0 1.4": ["placeable"], "1.8 18.5 8.2": ["demarkation"], "-2.6 1.4 10.4": ["unfluoridated"], "14.7 12.4 3.1": ["nastygrams"], "18.5 11.7 10.3": ["souvenired"], "38.6 4.6 16.0": ["snackfood"], "18.7 13.9 21.6": ["fuhgeddaboutit"], "5.4 10.3 8.3": ["huntelaar"], "11.3 5.3 17.5": ["calcine"], "10.0 8.2 12.2": ["nrk"], "15.7 4.1 10.1": ["thenardite"], "11.0 4.4 13.0": ["midround"], "9.2 0.4 11.2": ["sarira"], "6.0 3.7 4.7": ["audtions"], "10.3 14.3 18.7": ["lebih"], "1.5 -0.4 13.0": ["recanalisation"], "2.9 20.7 9.0": ["manipulativeness"], "15.0 3.4 18.9": ["bickies"], "-1.4 11.0 16.0": ["pregaming"], "8.2 6.6 5.5": ["togrow"], "9.9 9.7 5.4": ["unsnarling"], "15.7 12.8 11.1": ["semidesert"], "5.7 5.5 15.1": ["silverpoint"], "13.9 7.5 9.2": ["inchs"], "5.9 -2.6 16.1": ["cyntaf"], "1.8 8.5 7.2": ["fromhis"], "2.9 22.4 4.6": ["speakable"], "9.9 7.0 5.4": ["tofurther"], "7.5 9.3 9.6": ["mercurially"], "0.6 -6.3 7.1": ["scheuled"], "5.7 13.3 10.9": ["jouissance"], "7.5 2.6 2.0": ["rgod"], "7.2 3.5 9.2": ["postp"], "18.0 3.2 32.1": ["myrtles"], "0.4 3.5 -2.7": ["emminent"], "3.1 1.4 12.6": ["southampton"], "-3.1 16.2 8.5": ["everydown"], "7.5 -5.5 6.7": ["tals"], "11.8 7.8 15.1": ["plummer"], "2.4 16.3 3.3": ["indescretions"], "12.6 0.8 19.9": ["maltipoo"], "12.1 5.0 6.7": ["disassembler"], "13.4 -1.6 12.4": ["tootles"], "2.3 10.2 19.8": ["kotse"], "13.9 6.4 8.2": ["weibo"], "10.6 1.3 9.2": ["carfare"], "-7.5 3.3 4.1": ["transp"], "5.8 11.6 13.7": ["amygdalin"], "-3.6 19.1 9.5": ["negativeness"], "5.7 11.5 -4.4": ["alcolock"], "-1.7 7.2 15.3": ["promply"], "11.6 5.7 -2.4": ["thatits"], "0.6 19.3 8.0": ["denotations"], "10.4 9.1 15.1": ["pachuco"], "11.2 13.1 29.0": ["fishkeeping"], "-0.2 -3.1 8.7": ["preterminated"], "14.2 -1.9 11.2": ["ultradeepwater"], "2.9 13.5 4.6": ["millenarianism"], "1.2 7.4 19.6": ["turncoatism"], "19.6 9.3 8.0": ["pissoir"], "3.2 7.4 -0.3": ["winfuture"], "-2.5 -1.5 3.6": ["ornithine"], "5.2 15.2 13.1": ["stickfu"], "-1.0 9.9 3.9": ["restitutionary"], "8.2 2.5 22.5": ["pippin"], "7.5 8.8 15.6": ["kry"], "6.7 2.0 7.5": ["recinded"], "6.7 10.5 8.7": ["noodge"], "7.2 1.1 36.9": ["isda"], "15.9 11.6 6.9": ["curency"], "6.4 10.2 11.8": ["kuccha"], "1.1 -2.3 10.1": ["bulldoggers"], "-0.5 1.6 4.3": ["innerhalb"], "4.5 14.8 8.6": ["spelen"], "-8.6 8.3 11.6": ["euvolemic"], "9.3 5.7 34.6": ["sopaipillas"], "2.9 1.9 -0.7": ["teletherapy"], "9.4 5.1 11.6": ["stonkingly"], "6.6 12.8 16.1": ["sinked"], "16.7 11.5 22.5": ["dauer"], "1.4 27.1 0.6": ["incriminations"], "4.8 8.5 6.8": ["judaism"], "4.6 3.4 8.1": ["jscript"], "9.2 6.2 11.1": ["toteexacta"], "3.0 10.2 9.3": ["renormalization"], "4.8 5.8 12.0": ["pruno"], "9.3 29.5 11.2": ["fallenness"], "-4.5 2.9 -8.4": ["succe"], "17.1 3.4 7.0": ["curvacious"], "10.4 1.9 5.8": ["oulook"], "10.4 11.8 18.8": ["blizzardy"], "15.8 -2.8 18.9": ["chian"], "17.7 11.1 14.6": ["relandscaped"], "17.1 -1.4 13.0": ["craftmaking"], "15.4 19.3 20.9": ["gusanos"], "10.6 15.5 4.4": ["darty"], "0.5 0.7 6.2": ["mpbs"], "-4.1 10.2 6.2": ["baatein"], "16.3 19.8 13.0": ["goatse"], "11.0 2.8 12.4": ["doowop"], "-2.5 12.1 -2.1": ["comparism"], "5.2 11.2 3.3": ["plethysmograph"], "13.4 15.7 27.3": ["garum"], "11.3 22.4 11.6": ["flagless"], "4.5 -1.2 5.1": ["hardfacing"], "9.9 2.0 1.7": ["percemt"], "1.0 4.4 12.2": ["peeche"], "-5.1 19.3 7.2": ["synaesthete"], "14.4 16.4 19.0": ["aqualung"], "4.6 3.7 -3.2": ["emplane"], "7.3 6.2 15.7": ["undeducted"], "11.1 13.2 11.5": ["swaging"], "1.6 3.1 11.2": ["whokill"], "1.9 11.9 12.3": ["dottiness"], "9.8 -2.3 14.8": ["xe"], "14.3 -1.0 38.5": ["papardelle"], "5.4 4.6 14.9": ["bridals"], "2.0 -3.2 7.2": ["fieldman"], "7.4 8.4 7.6": ["formes"], "3.0 15.7 13.7": ["sortilin"], "8.0 2.2 9.5": ["quincentenary"], "17.4 17.3 1.6": ["retrive"], "7.8 14.9 4.2": ["respresent"], "15.9 5.1 20.0": ["siggi"], "7.3 -7.2 4.3": ["annuel"], "8.8 16.5 8.5": ["nomore"], "0.4 -6.2 9.7": ["browlift"], "8.5 -2.6 -2.1": ["leider"], "1.0 25.2 11.9": ["idealogies"], "4.1 -1.4 7.7": ["astemizole"], "10.9 16.6 13.8": ["collusively"], "-1.8 16.6 9.9": ["biradari"], "9.5 3.5 10.3": ["llowing"], "1.9 17.0 10.1": ["autoantigens"], "7.6 6.2 8.0": ["intracavitary"], "1.1 -0.2 13.8": ["additionals"], "10.3 23.7 3.4": ["aggrandise"], "20.3 0.9 5.4": ["nanomembrane"], "2.0 0.9 3.0": ["eforea"], "2.6 12.0 2.4": ["tawarruq"], "17.9 18.9 19.0": ["ooooooh"], "9.7 5.0 18.9": ["arabidopsis"], "8.5 3.9 9.5": ["ilu"], "12.4 7.9 6.9": ["activa"], "4.6 15.9 13.2": ["pefectly"], "13.8 10.1 10.6": ["stickhandles"], "6.8 5.0 9.9": ["hyperthreaded"], "9.3 10.4 18.3": ["gigue"], "8.6 17.3 19.4": ["canuck"], "6.4 -1.1 12.1": ["chanderi"], "-1.7 -0.6 5.9": ["ichannel"], "0.7 19.1 9.2": ["statebuilding"], "1.4 2.7 17.9": ["niente"], "11.0 28.8 9.1": ["nerfing"], "20.7 20.3 22.4": ["dagnabbit"], "8.1 4.6 -5.5": ["startet"], "15.4 -4.2 8.4": ["branche"], "-3.5 6.6 2.9": ["membres"], "13.4 -3.9 10.1": ["linerless"], "4.0 9.4 3.3": ["autodriver"], "19.3 8.2 17.6": ["hickies"], "8.6 2.4 7.7": ["cableways"], "10.8 11.5 18.9": ["naah"], "22.0 23.7 11.7": ["oligopolists"], "1.3 14.4 8.7": ["uncertaintiesthat"], "10.0 19.4 10.7": ["inadvisably"], "20.8 4.1 -2.8": ["vroomed"], "7.4 9.0 -0.3": ["insititutions"], "17.1 9.9 25.4": ["mittened"], "-1.9 12.2 13.1": ["carvacrol"], "4.3 -3.4 11.3": ["isme"], "2.3 14.5 8.4": ["coonery"], "20.9 1.1 1.4": ["aleader"], "-4.0 5.4 -7.3": ["counterpulsation"], "8.0 9.4 10.8": ["canonicalization"], "-4.2 15.4 -2.5": ["calld"], "15.5 -1.5 11.6": ["operaters"], "9.4 16.8 2.9": ["decending"], "1.4 5.8 11.0": ["susie"], "5.6 30.3 3.1": ["razakars"], "5.3 4.6 16.7": ["pich"], "2.0 19.2 5.5": ["economism"], "-4.6 5.9 -3.4": ["dispossesed"], "-0.1 3.5 5.3": ["pedorthist"], "24.1 0.8 8.3": ["ompanies"], "16.2 19.0 10.9": ["slipstreams"], "24.6 14.2 0.5": ["defrauder"], "2.0 4.6 -1.0": ["minsitry"], "13.0 -2.6 19.7": ["bue"], "10.8 5.2 20.5": ["junque"], "-1.3 3.5 9.7": ["surrogacies"], "1.6 5.8 4.7": ["urocortin"], "-3.4 7.3 8.7": ["interlined"], "15.3 8.1 34.6": ["whitecoat"], "8.9 9.7 9.5": ["enbankment"], "11.6 1.9 1.6": ["encylopedia"], "7.1 18.6 1.9": ["monads"], "10.3 8.0 2.6": ["broght"], "-1.2 1.0 6.5": ["suprapubic"], "16.3 26.5 14.5": ["neolib"], "23.2 11.2 2.6": ["samll"], "2.6 16.1 -0.9": ["homezone"], "6.4 21.7 0.9": ["routinization"], "11.3 23.6 7.6": ["whups"], "9.7 16.1 24.8": ["freshie"], "13.3 22.0 6.0": ["putridity"], "9.5 8.0 10.0": ["dewan"], "4.0 10.8 13.2": ["centaury"], "9.5 5.5 4.4": ["enigmatology"], "0.2 2.8 -6.3": ["beltpacks"], "-0.6 12.4 -2.7": ["indiscrimination"], "7.2 17.2 13.9": ["richochet"], "5.8 28.0 12.7": ["ourselfs"], "9.6 5.2 12.6": ["destin"], "20.1 7.5 9.2": ["companyis"], "-10.5 12.6 2.4": ["nazir"], "8.2 18.9 6.1": ["emotionalize"], "9.1 14.0 8.7": ["sexified"], "-5.4 9.2 4.9": ["communitites"], "8.0 1.0 29.1": ["puttu"], "3.1 10.8 7.6": ["pastorale"], "20.4 -2.1 6.7": ["reort"], "7.0 1.6 10.4": ["bauxites"], "-0.6 -1.4 -0.1": ["respitory"], "-5.1 2.8 2.9": ["plethysmography"], "6.9 9.8 31.7": ["sportfisherman"], "10.0 23.6 13.3": ["retrograding"], "7.2 4.1 10.2": ["anticrisis"], "16.4 20.8 18.9": ["buttholes"], "10.2 4.6 13.0": ["watters"], "7.9 9.0 13.6": ["deoxygenation"], "1.5 5.0 7.6": ["inexpensiveness"], "8.3 -1.6 7.7": ["certanly"], "16.0 7.5 2.2": ["chemoinformatics"], "2.9 24.7 6.7": ["dualisms"], "0.1 7.9 3.6": ["nickfaces"], "4.7 3.6 8.7": ["vaughan"], "8.9 11.6 13.5": ["sinlge"], "-2.2 3.6 6.0": ["superprime", "emai"], "9.9 6.0 6.9": ["inand"], "2.3 10.4 12.5": ["reassortant"], "0.1 -0.1 -4.8": ["rbg"], "8.5 12.1 5.0": ["variator"], "9.5 9.8 3.2": ["pusing"], "3.5 12.2 9.2": ["microswitches"], "-0.6 1.3 10.6": ["lipogenesis"], "0.6 10.2 14.2": ["prefilter"], "3.4 18.8 5.4": ["khanate"], "5.6 9.9 12.0": ["khipus"], "9.6 6.3 9.4": ["tiangges"], "0.5 28.1 10.7": ["unrestrictedly"], "11.3 9.3 12.3": ["crackups"], "4.7 6.5 0.0": ["echter"], "15.5 8.7 16.7": ["stereograph"], "10.4 5.8 5.3": ["tryptamine"], "7.3 -4.7 3.0": ["applica"], "-5.9 7.4 12.6": ["parasitaemia"], "-0.3 -1.6 11.0": ["hyperlipidemic"], "27.3 13.5 17.7": ["saurian"], "5.5 11.8 2.1": ["sprechen"], "1.1 2.6 3.6": ["extrapulmonary"], "-1.5 7.4 5.8": ["tragicomedies"], "7.2 22.8 10.9": ["argumen"], "13.8 4.1 47.1": ["tarakihi"], "8.9 13.7 3.3": ["catastropic"], "10.5 -1.8 13.3": ["gz"], "6.3 -0.4 11.4": ["sashing"], "4.3 9.2 13.6": ["thornton"], "11.2 7.3 8.0": ["extented"], "11.3 1.7 11.3": ["carper"], "15.8 11.6 13.8": ["profligates"], "4.3 -0.8 12.9": ["rhai"], "9.3 13.7 13.7": ["explo"], "2.7 -5.7 4.0": ["rema"], "2.7 10.4 26.3": ["gleaner"], "0.7 13.3 4.2": ["purgatives"], "8.4 6.1 5.9": ["ouverture"], "1.4 -10.4 -0.6": ["implantables"], "7.5 6.8 4.1": ["onyl"], "18.5 9.3 8.1": ["admakers"], "14.1 11.7 45.2": ["scungilli"], "13.4 3.9 0.9": ["qurter"], "17.8 10.8 20.5": ["poofing"], "15.2 -3.4 11.2": ["ligger"], "5.6 10.7 4.7": ["unblighted"], "-1.1 12.8 9.3": ["househelps"], "-1.8 17.0 11.6": ["swer"], "-2.9 9.6 16.5": ["hoye"], "-1.3 1.9 9.8": ["gelcap"], "10.6 2.3 8.7": ["subconjunctival"], "10.8 1.9 25.4": ["floorcloth"], "5.9 1.3 7.6": ["winnipeg"], "15.3 4.4 12.6": ["patternless"], "8.6 1.2 10.7": ["quem"], "19.4 19.3 16.6": ["touchie"], "1.4 10.5 7.1": ["multipartisan"], "-6.7 5.9 3.5": ["exceedence"], "16.0 16.7 11.4": ["nondoms"], "-1.3 7.4 10.7": ["economicdevelopment"], "10.9 7.6 26.6": ["avial"], "11.3 23.5 26.6": ["starthistle"], "12.0 21.2 19.0": ["claustrophobics"], "11.4 13.7 29.3": ["linnets"], "5.8 7.3 8.8": ["risksassociated"], "3.2 11.5 13.2": ["chete"], "10.0 15.6 6.0": ["leaguies"], "17.6 15.3 15.5": ["habours"], "-0.7 3.2 14.1": ["fairfax"], "9.0 3.3 11.7": ["studentification"], "10.1 34.7 9.2": ["alienness"], "7.7 6.9 11.1": ["uban"], "4.4 19.8 6.2": ["aion"], "17.0 4.6 29.1": ["cardboardy"], "-2.8 -2.7 11.2": ["ulster"], "10.8 5.9 12.5": ["ferdinand"], "13.0 11.6 4.5": ["interesing"], "3.0 28.3 -6.3": ["civilianised"], "13.0 1.4 2.4": ["anestimated"], "5.3 2.4 4.3": ["roadcourse"], "11.0 15.4 8.4": ["algebraically"], "10.7 7.1 15.2": ["snuggies"], "4.7 11.5 13.2": ["folkiness"], "9.4 6.8 13.7": ["multiphonic"], "12.6 8.4 15.0": ["metalists"], "16.4 9.5 15.8": ["cringeing"], "-2.6 -2.9 3.1": ["toreceive"], "11.0 16.1 9.8": ["mathmatical"], "17.0 5.3 16.4": ["addictives"], "-4.2 0.5 5.0": ["octathlon"], "10.2 12.0 7.3": ["iri"], "10.9 16.0 7.9": ["stockage"], "2.9 -5.1 2.7": ["populaires"], "3.6 9.3 -3.2": ["goalkeepr"], "16.1 -2.8 6.2": ["cameral"], "15.4 6.1 26.9": ["wherry"], "7.1 18.1 22.0": ["oyinbo"], "1.8 8.3 6.8": ["semitones"], "-0.9 12.7 6.7": ["stricly"], "0.1 7.0 17.7": ["sundowning"], "1.9 1.7 4.4": ["quizmasters"], "9.3 3.9 22.9": ["creamily"], "5.2 24.0 9.7": ["somekind"], "13.4 18.8 15.7": ["lionsault"], "0.8 10.9 6.9": ["duplicatable"], "-2.6 -3.6 1.7": ["contibutions"], "11.7 22.6 16.1": ["hyperawareness"], "7.6 11.2 26.2": ["hebe"], "5.2 9.9 3.4": ["warrantor"], "-7.5 9.6 6.9": ["inacted"], "12.6 9.3 15.1": ["staffy"], "4.8 17.8 10.9": ["diffence"], "-6.0 16.2 5.9": ["touble"], "10.5 5.9 17.4": ["philtrum"], "-2.1 24.6 5.3": ["forgoten"], "14.9 6.8 24.9": ["zapote"], "7.9 9.7 10.8": ["affixation"], "17.1 0.6 23.2": ["morganite"], "9.3 12.8 13.1": ["thows"], "3.0 8.5 14.9": ["sorte"], "4.3 13.3 6.5": ["policys"], "3.6 7.2 0.9": ["waining"], "9.8 6.9 19.3": ["soja"], "-1.0 5.6 12.7": ["adulted"], "0.4 12.8 5.0": ["soapboxing"], "1.2 12.8 -9.7": ["indepence"], "9.2 2.3 6.8": ["mse"], "6.2 3.2 9.9": ["concertino"], "2.5 10.0 17.9": ["meee"], "21.4 6.9 13.2": ["plushes"], "10.4 11.8 20.0": ["parky"], "9.5 11.4 10.8": ["exmaple"], "12.9 20.3 21.1": ["disingenuity"], "-0.1 11.3 7.1": ["overinsured"], "10.4 1.1 -3.6": ["comdirect"], "1.4 0.1 5.0": ["floriculturist"], "-0.9 1.5 16.1": ["depende"], "13.5 7.2 17.3": ["bernanke"], "8.1 29.1 4.3": ["oppponent"], "7.6 9.7 5.9": ["opteron"], "6.1 7.9 7.4": ["polaris"], "13.3 9.6 36.8": ["forcemeat"], "-1.5 5.9 11.4": ["sevas"], "3.7 11.3 9.9": ["ecotoxicological"], "1.0 -3.4 12.9": ["ministock"], "11.5 34.5 9.3": ["revanchists"], "8.2 0.5 9.9": ["amyl"], "9.4 6.2 15.6": ["escudo"], "3.6 2.6 11.3": ["recompeted"], "-2.8 5.1 3.9": ["inecalcitol"], "15.4 19.2 14.1": ["woggle"], "0.8 6.4 13.7": ["stevenson"], "-6.1 12.2 5.0": ["tutees"], "1.9 -2.8 -0.8": ["riskmanagement"], "-4.3 7.1 14.1": ["maaring"], "-5.3 2.9 -3.5": ["coache"], "1.9 9.0 7.9": ["webmistress"], "-0.6 9.4 1.9": ["notthe"], "-7.7 -1.1 -12.6": ["indorsed"], "13.6 4.2 4.7": ["blaggers"], "3.1 -3.7 8.4": ["foro"], "9.2 13.4 14.9": ["pissin"], "-0.5 12.4 -2.5": ["congolais"], "6.6 5.9 28.0": ["downeast"], "5.9 4.2 16.7": ["superferries"], "-7.7 8.8 7.3": ["restictions"], "6.6 19.0 13.7": ["fuggin"], "20.8 15.4 21.8": ["balalaikas"], "14.8 6.5 10.1": ["analaysts"], "13.5 27.4 4.1": ["rapprochment"], "-3.7 6.8 11.9": ["nonreportable"], "3.1 1.6 13.3": ["pote"], "4.6 10.6 12.2": ["celcius"], "-3.9 4.1 9.5": ["kutcheri"], "-4.3 6.1 9.1": ["cohabitations"], "2.0 18.7 14.4": ["outbattling"], "6.7 -3.4 7.4": ["govenors"], "2.4 9.6 5.6": ["turgidly"], "5.5 5.7 7.9": ["railfan"], "1.6 -0.9 12.1": ["proanthocyanidin"], "1.2 9.2 15.5": ["grandmotherhood"], "1.1 -0.7 10.5": ["maaaring"], "9.2 8.0 10.8": ["multiserver"], "11.8 6.2 10.0": ["almos"], "11.6 15.2 25.3": ["tchr"], "-1.3 20.2 4.7": ["unfairnesses"], "8.2 2.6 1.3": ["bimolecular"], "4.1 2.2 0.1": ["efaproxiral"], "8.7 9.8 14.4": ["actitivies"], "5.8 10.6 19.3": ["fellings"], "-1.0 17.9 22.3": ["rachis"], "-6.5 11.1 12.9": ["suchstatements"], "16.6 19.4 41.9": ["hawgs"], "20.7 11.6 24.8": ["batwings"], "8.1 23.0 4.7": ["controlls"], "1.2 19.2 1.9": ["stateman"], "9.7 6.1 26.4": ["rosella"], "3.8 10.6 14.1": ["closeto"], "6.1 6.6 28.9": ["flitches"], "4.8 11.1 -0.2": ["echnology"], "9.5 2.7 8.7": ["purdue"], "17.0 1.7 24.4": ["boxships"], "0.7 5.6 13.8": ["basketing"], "19.4 7.3 36.2": ["rockpool"], "1.1 11.2 8.0": ["windies"], "21.5 10.1 0.0": ["masterbrand"], "6.9 1.8 19.2": ["uta"], "5.4 2.3 15.1": ["preretirees"], "-4.8 1.4 11.3": ["nakapag"], "12.0 1.1 9.8": ["leucoxene"], "4.7 -1.5 10.3": ["adroddiad"], "6.1 0.9 6.5": ["amc"], "2.4 3.5 7.2": ["overbuilds"], "15.8 0.6 25.9": ["taho"], "11.1 10.0 13.9": ["prudishly"], "7.6 16.0 -1.0": ["inalienably"], "2.0 17.3 26.9": ["pepperweed"], "13.0 11.0 4.4": ["conflations"], "5.2 15.9 15.0": ["kalau"], "2.2 18.4 23.3": ["wingshooters"], "10.3 16.8 27.7": ["goutweed"], "16.9 2.1 21.3": ["quatrefoil"], "2.8 10.5 5.1": ["wvu"], "-1.2 2.5 7.1": ["artmuseum"], "3.8 8.7 3.6": ["chieftancy"], "11.1 12.1 15.5": ["louie"], "1.7 14.1 12.4": ["neoteny"], "-1.8 3.1 6.0": ["plasty"], "20.0 9.6 3.1": ["photomosaic"], "-0.0 7.3 1.8": ["comparible"], "-1.7 23.1 -13.8": ["denigrations"], "-4.3 8.4 12.0": ["referals"], "7.6 18.2 19.7": ["unpalatably"], "2.9 -3.4 6.6": ["metabolics"], "1.1 15.1 13.1": ["pentamidine"], "5.7 35.4 13.8": ["reinvading"], "3.9 1.7 8.7": ["creampie"], "2.2 5.8 7.5": ["maneb"], "3.6 2.8 1.9": ["downstreamed"], "7.2 21.7 22.9": ["boathandling"], "5.2 1.2 6.8": ["exchangeability"], "8.3 10.3 10.0": ["leafiest"], "-4.0 13.8 0.3": ["mohallah"], "4.1 -3.9 12.9": ["krishi"], "4.9 6.8 15.5": ["stringband"], "-6.8 14.8 12.7": ["vegetar"], "-4.0 3.7 -3.1": ["pantagraph"], "-1.0 -0.6 -0.5": ["andrologist"], "18.8 9.4 15.5": ["perambulator"], "7.5 17.3 27.1": ["manuring"], "5.7 20.0 5.5": ["monistic"], "-1.1 11.9 8.6": ["encourging"], "3.1 6.1 13.8": ["vul"], "21.8 19.9 10.8": ["cogwheels"], "-2.9 4.6 2.7": ["compensatable"], "4.7 3.4 15.1": ["thefourth"], "9.0 23.1 6.7": ["agoraphobics"], "-0.7 11.2 13.0": ["dopa"], "6.5 12.6 19.7": ["nontropical"], "3.1 11.1 8.7": ["occupiable"], "6.9 6.1 5.3": ["kendall"], "-6.0 5.0 6.0": ["ccr"], "2.2 18.2 -5.4": ["justic"], "9.9 22.9 17.0": ["gooning"], "7.4 25.6 18.2": ["suppliant"], "10.4 4.2 14.3": ["regas"], "12.5 21.2 10.3": ["trammels"], "14.1 13.6 6.3": ["apodyterium"], "20.3 0.6 23.0": ["capiz"], "4.9 -4.6 1.3": ["inclued"], "16.6 -0.9 3.1": ["theagreement"], "1.9 10.3 8.9": ["osteolytic"], "-0.6 2.6 9.0": ["swindon"], "-2.9 6.3 6.8": ["karim"], "-1.1 3.5 12.1": ["origine"], "-1.7 -6.9 -8.8": ["heimer"], "8.0 9.4 15.0": ["dolore"], "3.7 -8.9 -0.3": ["promting"], "1.5 5.6 -7.0": ["interbanking"], "15.1 14.2 19.4": ["starin"], "4.3 11.5 -0.4": ["signalised"], "13.0 6.5 5.4": ["hullo"], "4.8 17.4 12.7": ["epiglottitis"], "4.8 -5.2 26.1": ["gher"], "4.6 15.3 2.2": ["frachise"], "7.3 -0.5 2.4": ["siliconindia"], "12.9 7.4 9.6": ["dandling"], "14.4 -0.6 2.5": ["subtantial"], "3.7 11.7 4.6": ["magnetometric"], "10.4 13.9 10.3": ["kille"], "16.7 17.8 14.2": ["slumberous"], "-3.6 1.1 3.9": ["miutes"], "11.7 9.8 11.7": ["acrostics"], "18.0 1.3 12.8": ["halifax"], "6.3 -0.5 3.9": ["cyclase"], "11.6 14.6 18.5": ["monocropping"], "5.7 6.7 19.5": ["avermectin"], "18.0 9.7 14.4": ["clackety"], "1.5 14.8 10.7": ["asymptomatically"], "-3.0 11.6 -4.6": ["leadersip"], "0.8 9.0 11.7": ["shuru"], "0.4 -2.3 -1.1": ["whatsnew"], "7.0 9.5 -1.4": ["projectory"], "0.2 6.0 6.8": ["llega"], "1.2 0.4 -2.5": ["wbd"], "6.7 8.0 8.8": ["underrepresents"], "13.0 -5.9 12.4": ["theopening"], "2.1 1.5 12.9": ["virginiamycin"], "7.5 2.0 17.7": ["wheatish"], "10.4 6.2 1.7": ["repairperson"], "9.7 13.0 9.1": ["orthorectified"], "5.8 6.8 14.7": ["avulsed"], "23.0 8.1 13.2": ["junkiest"], "0.4 10.3 10.3": ["concusion"], "10.6 4.0 11.7": ["slutting"], "4.4 23.9 6.2": ["knowledged"], "22.0 10.1 1.5": ["potrait"], "11.2 5.9 14.5": ["harshed"], "5.8 11.1 11.3": ["forecastable"], "13.8 13.2 16.6": ["cellulites"], "11.4 12.1 7.3": ["minbar"], "10.7 7.2 8.5": ["paralized"], "10.3 -1.9 5.0": ["vif"], "9.8 4.0 16.9": ["ddim"], "14.2 7.9 6.6": ["outstreched"], "14.1 11.8 14.0": ["proppy"], "3.5 11.2 6.4": ["teetotalism"], "12.8 8.5 15.4": ["undynamic"], "8.7 13.6 16.3": ["asphyxiates"], "8.7 16.8 25.6": ["gazanias"], "-1.6 31.0 7.6": ["unmilitary"], "16.0 10.8 16.7": ["kolanut"], "5.5 23.6 5.3": ["annihilationist"], "15.8 -0.4 16.6": ["maltster"], "8.1 7.7 23.1": ["limy"], "-4.1 11.4 8.2": ["astatine"], "5.2 15.0 24.0": ["grover"], "8.0 16.9 10.0": ["decremented"], "-4.1 18.8 3.7": ["constiuents"], "-1.3 -2.6 1.5": ["rer"], "5.2 7.8 9.8": ["banjar"], "7.1 5.5 11.2": ["volunteeers"], "-2.4 5.2 9.3": ["captan"], "11.0 14.9 19.2": ["restained"], "1.1 2.9 7.8": ["examen"], "1.5 25.8 7.1": ["armes"], "4.3 5.6 2.1": ["torrented"], "8.3 -2.4 1.8": ["macitentan"], "9.7 16.0 3.2": ["multiaxis"], "18.5 3.1 25.9": ["shiplap"], "10.0 -3.6 0.8": ["risultati"], "10.9 7.6 5.1": ["multiprocess"], "4.6 -1.4 14.0": ["decs"], "13.7 4.9 33.2": ["tikoy"], "13.2 1.7 27.4": ["bote"], "22.3 10.3 17.5": ["slaphead"], "-6.9 -1.9 -2.4": ["advis"], "6.3 -2.6 11.3": ["cynllun"], "12.4 25.2 22.8": ["marauds"], "-5.5 7.9 12.3": ["osha"], "-4.0 -2.2 6.4": ["erty"], "-4.2 4.9 -0.8": ["tps"], "-8.4 9.3 5.8": ["emended"], "-5.2 5.8 0.7": ["attorny"], "6.2 5.6 7.2": ["soulsters"], "16.0 13.4 44.1": ["trepang"], "5.9 -2.2 4.9": ["conradm"], "8.4 8.1 13.7": ["percapita"], "17.6 18.5 13.2": ["extraterrestial"], "1.6 12.6 16.2": ["kerana"], "-0.7 15.1 9.8": ["educrat"], "4.1 4.6 5.2": ["prelisting"], "9.3 8.1 12.5": ["herbert"], "-8.5 8.4 1.5": ["rearrests"], "-0.9 8.0 -0.7": ["json"], "2.4 8.6 7.0": ["readoption"], "-0.7 0.7 6.2": ["tuesdays"], "-2.5 -3.5 1.7": ["junio"], "-2.4 6.3 4.3": ["permis"], "19.4 17.4 17.3": ["jerkface"], "6.5 10.2 21.6": ["backcrossing"], "13.9 11.1 10.0": ["botellon"], "4.4 14.8 15.6": ["unfussily"], "9.6 7.0 28.3": ["rouladen"], "25.1 19.6 19.7": ["puniness"], "-0.5 -0.8 2.2": ["microgrant"], "1.5 2.5 7.5": ["tradeswomen"], "10.4 29.0 9.8": ["uncaringly"], "11.4 7.9 7.5": ["zoophiles"], "24.7 -0.4 20.3": ["temperas"], "1.6 9.2 -0.0": ["ethene"], "22.0 15.2 22.4": ["rassling"], "-1.3 9.3 5.1": ["gabbai"], "2.4 -5.9 8.8": ["estudio"], "12.9 24.2 7.8": ["mischaracterisation"], "5.2 19.4 7.7": ["emergancy"], "4.2 -9.7 2.8": ["earlie"], "8.5 25.1 22.9": ["anopheles"], "4.3 18.1 7.3": ["panchs"], "16.7 5.1 21.4": ["folkers"], "11.1 7.5 1.7": ["compettion"], "7.0 6.6 7.5": ["realmente"], "11.2 14.0 4.0": ["needa"], "10.7 -0.2 10.0": ["fecha"], "1.3 13.3 16.5": ["lotting"], "2.5 10.4 9.5": ["lesen"], "4.9 14.0 3.9": ["shanahan"], "14.1 26.8 20.5": ["jerkwad"], "29.4 -6.7 -3.7": ["subisidiary"], "3.1 -2.6 8.6": ["yeaer"], "6.8 9.3 21.3": ["wops"], "2.1 9.2 5.9": ["emply"], "1.2 3.7 17.7": ["madalas"], "5.8 2.3 15.2": ["carbonatized"], "9.2 6.0 15.4": ["cruch"], "-0.7 5.1 4.9": ["housemothers"], "2.5 -0.8 3.5": ["consectuive"], "22.0 4.6 5.8": ["multicompany"], "7.5 19.9 6.1": ["deorbiting"], "6.9 8.1 8.4": ["taxcuts"], "0.1 2.3 8.1": ["eanred"], "15.2 18.1 19.5": ["punchin"], "9.6 18.3 8.2": ["gelotophobia"], "1.3 9.1 13.3": ["digby"], "4.3 -0.8 12.4": ["alcuni"], "3.8 5.7 7.4": ["fansink"], "4.1 15.7 -2.6": ["noncredible"], "12.7 1.2 27.1": ["champignon"], "2.4 25.4 1.6": ["peackeeping"], "11.1 10.6 12.6": ["afriend"], "1.6 10.4 -1.6": ["nothign"], "-4.8 -0.9 7.7": ["pmm"], "3.8 2.4 9.7": ["sebastian"], "23.9 15.9 21.6": ["sleb"], "-2.5 7.1 8.1": ["tuberosity"], "-4.3 8.3 4.1": ["reaccommodate"], "-0.8 11.9 6.0": ["nomineee"], "16.2 18.8 14.9": ["screwin"], "2.9 13.3 -1.1": ["sanusi"], "7.8 6.9 8.5": ["apropriate"], "5.2 23.3 -0.2": ["ideologic"], "1.9 6.8 10.6": ["unemplyment"], "19.6 7.8 7.4": ["slingshotted"], "32.6 11.7 9.1": ["starshade"], "5.1 1.4 1.2": ["thequality"], "5.4 8.0 0.8": ["textese"], "3.7 -5.0 14.3": ["belo"], "13.2 11.1 0.6": ["telemetrics"], "8.4 14.9 5.1": ["rooom"], "3.8 5.5 2.9": ["langage"], "9.2 -0.9 -0.1": ["madeover"], "15.1 0.9 11.6": ["deisgn"], "2.2 20.2 -9.8": ["ldblquote"], "-4.1 23.0 5.0": ["followship"], "6.5 10.9 7.4": ["coincedence"], "5.0 4.3 17.1": ["dren"], "2.3 2.6 2.8": ["prositution"], "0.9 5.5 3.5": ["otologist"], "3.6 17.9 2.7": ["multidimensionality"], "9.6 3.0 19.4": ["dentate"], "8.1 18.3 13.3": ["hyperfocus"], "9.0 7.7 25.8": ["ruber"], "-4.0 1.4 6.4": ["ponte"], "4.7 5.4 10.7": ["marketand"], "0.3 11.2 16.7": ["ganon"], "3.7 9.4 9.8": ["mingers"], "11.1 10.7 0.4": ["ressurection"], "-8.1 22.6 -7.0": ["anathematized"], "18.2 42.1 6.6": ["starfighters"], "4.9 10.9 5.7": ["touchmonitors"], "16.2 13.8 26.7": ["ovenbirds"], "10.1 15.7 19.5": ["pured"], "17.9 3.5 -1.2": ["enterting"], "14.2 21.2 23.2": ["roundhead"], "2.3 20.3 10.7": ["outguessed"], "23.5 12.6 12.6": ["mildewing"], "13.1 10.1 15.0": ["enterobacteria"], "10.9 10.4 13.9": ["hydrographical"], "-1.6 27.1 -2.4": ["sayanim"], "13.2 6.6 14.8": ["halle"], "-5.6 7.3 -0.3": ["adminsitrative"], "6.4 35.2 3.1": ["civlian"], "10.9 8.6 28.8": ["parrillada"], "12.7 18.1 11.9": ["tombstoned"], "10.6 27.8 9.5": ["inalterably"], "1.1 8.9 13.3": ["hamartomas"], "4.9 6.2 22.0": ["marino"], "11.4 9.8 23.8": ["overbites"], "7.1 12.0 10.5": ["exostosis"], "18.6 31.0 21.5": ["witcher"], "9.2 9.5 4.4": ["strategises"], "16.2 34.9 14.8": ["asuras"], "10.2 13.4 17.0": ["histiocytes"], "-8.9 -1.9 7.1": ["semestral"], "11.8 6.7 12.0": ["brahman"], "0.2 3.5 13.5": ["katoeys"], "11.1 15.9 17.5": ["queendom"], "13.5 11.3 13.4": ["nanopillar"], "19.3 2.0 18.6": ["polkadot"], "-2.7 -2.0 -1.9": ["optimisitc"], "-1.9 0.9 -0.4": ["marian"], "8.4 7.7 26.7": ["oaty"], "8.1 -0.4 -1.5": ["relevations"], "13.6 20.7 15.5": ["mongerers"], "8.6 30.6 7.9": ["fanaticisms"], "17.4 16.5 20.9": ["astonishments"], "-5.1 7.4 7.3": ["predeceases"], "4.0 -1.4 -0.1": ["acuerdo"], "12.1 14.0 0.9": ["sledmates"], "7.5 16.1 12.9": ["unproductivity"], "-3.2 3.2 -6.7": ["unaminous"], "12.2 8.5 8.1": ["apses"], "9.8 34.0 3.9": ["treasonously"], "4.0 10.8 8.7": ["autobid"], "-3.0 5.0 10.7": ["lup"], "-2.6 30.1 -2.5": ["covertness"], "8.9 -1.1 2.9": ["turbogenerator"], "8.5 13.3 15.3": ["yagi"], "4.5 7.3 2.4": ["nition"], "8.4 1.1 11.4": ["coninue"], "-6.8 23.5 8.4": ["descript"], "15.0 9.8 21.5": ["sullage"], "5.9 18.1 5.3": ["bioelectrical"], "6.6 -0.8 4.0": ["stafff"], "-0.0 8.9 -0.1": ["resonded"], "19.4 5.8 6.7": ["aworld"], "-4.0 -1.8 10.1": ["chiari"], "15.7 13.9 14.5": ["microswitch"], "9.9 -0.4 11.9": ["charreadas"], "10.7 6.6 18.1": ["brightside"], "-2.2 18.6 1.5": ["complementariness"], "10.9 9.7 32.5": ["pochards"], "11.3 9.7 4.6": ["narks"], "12.4 3.1 13.6": ["metalloid"], "9.1 5.9 8.9": ["chalcogenides"], "10.4 7.4 6.1": ["thermopower"], "13.8 13.0 18.9": ["heav"], "12.1 14.4 18.7": ["midlatitude"], "9.8 18.9 14.1": ["scragging"], "11.4 6.6 25.9": ["sweetpeas"], "11.8 13.1 8.4": ["sysytem"], "5.5 4.7 5.4": ["finically"], "3.9 7.5 6.1": ["pueda"], "5.1 -1.6 1.0": ["otal"], "11.9 11.3 12.5": ["zeer"], "15.5 2.5 3.5": ["becomea"], "9.9 6.3 13.1": ["danseur"], "15.4 5.7 21.9": ["sansevieria"], "16.1 10.0 15.8": ["braaivleis"], "-1.9 15.5 8.5": ["subnetting"], "11.4 9.7 16.7": ["mys"], "6.0 19.6 4.5": ["psychohistory"], "-0.6 7.6 10.2": ["chakkar"], "-1.0 15.1 8.4": ["subluxated"], "-2.7 6.8 0.6": ["committted"], "7.6 2.5 7.7": ["microfibres"], "0.9 12.9 19.2": ["plaintiveness"], "15.2 -3.6 31.7": ["braeburn"], "21.0 2.0 17.3": ["sackload"], "12.4 25.8 6.9": ["messanger"], "3.5 4.6 10.8": ["wallrocks"], "21.5 -2.0 8.0": ["smarthome"], "2.4 -1.4 1.2": ["theorganization"], "11.2 4.6 31.9": ["passerine"], "6.1 8.8 38.8": ["dermo"], "-0.7 9.4 4.8": ["practi"], "7.9 -2.7 9.4": ["tencel"], "1.8 19.7 13.9": ["rosem"], "9.1 7.4 25.6": ["rasmalai"], "2.0 5.9 15.0": ["masakit"], "-4.2 -2.5 5.2": ["recipents"], "5.5 5.7 12.5": ["underpopulation"], "5.0 16.9 10.9": ["cogging"], "-2.4 3.9 15.0": ["meng"], "-5.0 15.4 4.5": ["planful"], "-4.0 9.0 -0.1": ["personably"], "-2.7 10.8 12.3": ["eightman"], "1.5 6.5 1.7": ["dox"], "-3.5 5.9 9.3": ["midde"], "15.0 -1.5 -2.7": ["corproate"], "19.9 6.7 19.0": ["pachanga"], "21.7 5.4 11.4": ["oompa"], "11.8 -0.4 32.9": ["sancocho"], "14.6 16.0 10.4": ["collimating"], "17.4 10.5 13.0": ["brighest"], "13.6 10.4 9.7": ["spryness"], "5.6 5.8 14.7": ["trouver"], "11.0 7.8 30.0": ["lichee"], "1.7 10.6 5.5": ["signalcallers"], "9.2 5.5 12.3": ["clammering"], "4.4 8.1 45.5": ["blackfishing"], "15.2 7.7 11.6": ["balancesheets"], "0.3 0.5 8.3": ["normale"], "8.6 4.8 -1.3": ["certificating"], "6.9 20.1 -1.4": ["stonethrowing"], "15.2 1.8 20.8": ["galv"], "9.8 6.1 12.3": ["crewnecks"], "7.3 4.6 -4.0": ["peration"], "6.4 25.6 6.8": ["beingness"], "4.5 6.9 7.7": ["padless"], "4.4 14.9 12.7": ["hypermethylated"], "10.7 21.7 2.8": ["understimate"], "12.1 13.4 24.6": ["migrational"], "-5.8 0.9 9.4": ["mented"], "-1.7 7.0 10.7": ["fasttracked"], "9.5 14.2 16.4": ["paraskavedekatriaphobia"], "8.5 6.5 12.4": ["hyperflexion"], "7.5 12.2 10.8": ["geodynamic"], "15.2 4.0 14.1": ["bespangled"], "0.1 23.2 2.4": ["nything"], "4.8 -4.0 24.8": ["beadlets"], "17.9 3.0 14.3": ["musicmakers"], "8.0 5.8 25.6": ["verdejo"], "4.8 6.7 3.6": ["subsequence"], "12.0 8.4 10.0": ["twowheeler"], "9.1 14.9 7.4": ["outin"], "6.9 16.2 2.0": ["suraksha"], "-0.0 10.8 4.1": ["unday"], "6.7 2.2 12.6": ["mineralogists"], "4.3 11.4 19.2": ["waltzy"], "9.1 13.0 -2.6": ["supernannies"], "16.8 10.4 3.8": ["handrest"], "8.7 9.7 7.5": ["midlatitudes"], "5.4 0.6 8.0": ["csd"], "5.1 5.5 -5.7": ["otcqb"], "17.0 14.7 28.4": ["greenland"], "-1.4 4.2 0.0": ["costsavings"], "12.5 -4.9 0.4": ["repackager"], "-2.7 9.9 7.4": ["nonrepresentative"], "9.7 1.4 13.3": ["microdistilleries"], "1.3 8.4 5.0": ["autocrossing"], "13.4 8.9 12.7": ["hotdoggers"], "-5.2 8.8 7.0": ["cyanazine"], "12.9 2.2 7.3": ["ovie"], "8.3 8.0 11.1": ["meaningfull"], "12.4 7.6 11.2": ["populi"], "-11.3 11.6 -0.9": ["gedolim"], "14.5 5.2 18.8": ["heathered"], "-3.2 7.2 -4.5": ["slained"], "7.6 12.9 11.8": ["drillstring"], "-0.3 9.0 7.1": ["talati"], "5.9 -1.4 24.5": ["deline"], "1.5 11.1 1.8": ["copers"], "-4.1 7.9 5.9": ["voluntaries"], "8.1 -0.6 3.8": ["superhead"], "6.1 1.0 9.3": ["petrological"], "12.5 14.7 7.4": ["customizeable"], "-1.4 34.5 3.5": ["salafists"], "4.5 23.2 4.9": ["diffuseness"], "9.7 22.3 2.2": ["antiterrorists"], "-6.5 1.7 5.6": ["canaloplasty"], "-2.9 5.2 4.3": ["grievor"], "10.5 28.5 15.0": ["gunless"], "3.0 13.4 4.4": ["mausi"], "0.3 6.0 11.3": ["coexpression"], "10.6 10.9 9.8": ["creepshow"], "-3.0 8.2 8.0": ["climat"], "10.9 6.4 -0.0": ["microelectromechanical"], "8.1 8.9 16.2": ["juist"], "11.4 9.2 3.4": ["gestern"], "9.5 10.9 11.4": ["outboarding"], "11.4 -1.8 17.3": ["ecoroof"], "10.3 12.6 4.9": ["effortsto"], "4.9 5.3 2.5": ["nouvel"], "8.4 12.1 12.7": ["nevah"], "9.8 12.5 15.2": ["hoicking"], "8.6 9.6 13.5": ["degas"], "3.0 13.2 13.2": ["propper"], "4.0 1.8 5.0": ["insurnace"], "6.4 2.5 13.4": ["kaveera"], "14.6 6.3 10.1": ["enkele"], "4.1 6.9 5.8": ["superspreaders"], "5.6 13.1 7.0": ["futu"], "-6.2 -4.1 -0.5": ["ppa"], "11.8 7.5 3.0": ["copromotion"], "1.8 11.1 8.8": ["therisk"], "8.6 18.9 20.0": ["unneccesarily"], "-5.2 8.5 4.4": ["azacytidine"], "-2.2 -7.9 6.7": ["yojna"], "-2.8 3.9 11.5": ["tient"], "6.6 0.2 7.0": ["rodder"], "11.1 11.4 9.6": ["microdroplet"], "8.1 -9.5 1.3": ["emea"], "-2.5 7.1 1.3": ["extraterritorially"], "3.3 2.3 11.4": ["jewell"], "13.7 6.0 8.0": ["booooo"], "7.8 3.0 0.8": ["pamplets"], "9.3 22.3 12.8": ["immeadiately"], "-7.8 3.4 1.9": ["menbers"], "-4.5 32.3 5.8": ["accommodationists"], "-0.6 6.9 5.7": ["scenarists"], "4.6 16.7 5.8": ["normies"], "8.3 -6.7 12.7": ["violinmaker"], "-11.1 1.1 -0.2": ["subcounty"], "-1.8 5.6 5.9": ["purohits"], "2.0 9.0 8.4": ["hudd"], "18.8 5.1 20.0": ["coffinette"], "-4.7 7.8 6.7": ["upzoned"], "13.5 7.5 20.0": ["eyecups"], "17.7 16.1 18.5": ["arachnophobic"], "12.5 10.6 27.3": ["marguerites"], "7.6 14.6 21.6": ["unjammed"], "7.5 12.5 31.5": ["sambals"], "14.7 25.5 8.5": ["unrestrainedly"], "11.7 -2.4 6.8": ["imagesetters"], "6.9 9.7 14.6": ["poltroon"], "1.2 7.9 14.0": ["haemolysis"], "19.6 25.4 14.1": ["bandidos"], "11.5 7.1 31.3": ["dieoff"], "-9.0 3.8 -5.2": ["unadmitted"], "13.8 18.6 8.1": ["unfillable"], "14.2 15.4 16.7": ["amoeboid"], "-4.5 4.1 2.0": ["prt"], "24.1 3.4 6.4": ["gloabl"], "3.7 5.3 7.3": ["maknae"], "11.1 29.3 12.4": ["molotovs"], "12.8 12.2 9.8": ["gamespot"], "4.4 2.3 8.9": ["tweep"], "7.6 12.6 12.2": ["econimic"], "4.8 11.7 21.4": ["cere"], "-4.0 18.8 8.8": ["minhag"], "3.3 17.2 4.4": ["drow"], "8.8 3.1 18.0": ["kinome"], "13.5 4.8 22.0": ["criolla"], "10.2 1.6 14.7": ["raffinate"], "12.0 18.2 3.5": ["consumerists"], "15.7 11.4 9.1": ["fortess"], "17.8 -5.7 9.0": ["corsa"], "11.3 -2.9 9.8": ["sheetrocking"], "1.5 18.4 4.8": ["extrinsically"], "4.4 1.2 3.7": ["rati"], "14.3 4.1 19.5": ["baywalk"], "-1.9 -1.2 16.6": ["sfn"], "17.4 16.7 13.4": ["subsidizer"], "3.5 14.6 14.9": ["khair"], "20.8 1.5 19.6": ["hyperscale"], "4.2 3.3 16.0": ["pondo"], "4.6 21.0 6.3": ["homosex"], "1.7 14.1 10.9": ["mandalam"], "10.6 15.5 6.2": ["potental"], "12.1 11.5 28.0": ["tteok"], "1.2 -1.8 10.0": ["shirtwaists"], "15.3 1.0 22.1": ["rockwool"], "4.5 16.9 0.9": ["politcial"], "3.8 10.1 8.8": ["realiable"], "7.6 24.7 12.3": ["uglify"], "-5.7 0.5 1.7": ["superannuate"], "-0.6 6.2 16.5": ["subtrades"], "4.0 -0.5 11.5": ["asu"], "1.8 3.2 1.1": ["centrex"], "7.2 26.4 19.4": ["zugzwang"], "9.7 13.9 1.1": ["propulsions"], "0.6 -0.2 11.8": ["sert"], "9.1 19.4 4.4": ["unguessable"], "2.4 19.8 3.9": ["diffusible"], "6.0 -0.0 15.0": ["gawing"], "-4.6 2.8 10.9": ["hypercalcaemia"], "14.8 12.1 20.4": ["tej"], "-5.7 -0.7 1.9": ["professonal"], "-0.4 9.7 7.2": ["biologies"], "0.2 9.3 11.9": ["conocer"], "-4.3 18.5 4.3": ["nakabandis"], "17.8 15.5 17.1": ["sordidly"], "10.3 -0.7 -3.3": ["pnds"], "18.6 11.0 11.6": ["charka"], "9.6 11.2 12.1": ["sondes"], "12.5 10.8 8.6": ["catastrophist"], "7.9 9.9 13.6": ["tramming"], "16.6 15.4 10.3": ["grimed"], "0.4 8.4 1.7": ["underdose"], "0.7 10.0 -2.2": ["forefeit"], "-5.2 25.8 6.3": ["galut"], "18.8 2.8 9.9": ["llion"], "12.0 7.5 19.5": ["organzas"], "9.7 8.2 10.8": ["chiasmus"], "15.5 3.7 12.4": ["amillion"], "12.6 17.6 12.5": ["spoonerism"], "13.6 14.2 7.9": ["toavoid"], "-0.6 16.2 9.3": ["savegames"], "1.9 10.9 17.2": ["itne"], "12.7 9.4 19.8": ["clowny"], "-0.6 2.5 22.1": ["tari"], "4.6 13.6 3.3": ["brigadistas"], "5.1 0.4 8.5": ["lactitol"], "3.3 4.7 11.2": ["vascularisation"], "9.5 3.4 15.2": ["parasitologists"], "16.0 7.7 4.2": ["showboaters"], "12.9 7.6 20.2": ["floatover"], "16.0 10.5 32.0": ["sopapilla"], "8.1 -4.9 -2.3": ["hpc"], "12.3 22.4 10.5": ["delaminations"], "6.5 23.1 15.7": ["whereto"], "-3.0 8.2 4.0": ["airpoints"], "12.7 16.0 8.8": ["antiform"], "-2.5 -3.9 18.4": ["birthweights"], "10.3 4.9 6.8": ["motelier"], "2.3 0.2 1.9": ["rehabilitaion"], "18.5 12.2 8.7": ["superlobbyist"], "11.7 16.4 9.2": ["academicism"], "-8.6 10.0 4.1": ["alfentanil"], "-0.4 -0.8 14.1": ["mportant"], "-10.5 5.5 -5.1": ["exida"], "9.0 4.5 2.7": ["soccers"], "8.9 2.8 5.7": ["aerobar"], "8.4 15.3 12.8": ["bolly"], "3.3 -3.4 12.8": ["captively"], "15.1 -4.3 3.3": ["appls"], "7.8 4.1 11.4": ["plumpers"], "17.8 -1.0 13.2": ["ironsands"], "-1.8 -0.8 3.8": ["acepromazine"], "23.7 10.7 20.1": ["geomancers"], "-1.2 8.1 6.5": ["hursday"], "13.8 8.2 13.9": ["circusy"], "2.5 4.0 12.6": ["chalta"], "0.5 8.2 0.6": ["tipifarnib"], "-7.4 0.5 5.5": ["inhibin"], "2.5 24.4 3.2": ["unclever"], "15.2 -2.8 15.2": ["flrs"], "9.0 14.0 13.5": ["mumma"], "15.0 5.1 21.5": ["fuschias"], "1.5 2.6 6.4": ["propiconazole"], "-9.3 2.0 11.6": ["reachedat"], "14.9 3.4 -1.2": ["ithad"], "3.2 2.1 6.2": ["theglobe"], "-1.3 26.3 6.1": ["conditionings"], "15.4 0.8 7.0": ["purchas"], "3.0 11.6 10.5": ["perserving"], "10.1 -6.3 5.0": ["prodotti"], "-0.2 -7.1 3.2": ["anagement"], "6.7 1.0 39.8": ["setnet"], "18.2 25.6 5.9": ["petrostate"], "3.6 1.6 6.6": ["vered"], "2.7 10.7 1.8": ["reverter"], "9.9 21.6 5.0": ["glocalization"], "-3.6 11.0 8.4": ["prettty"], "5.6 6.8 6.1": ["goys"], "6.1 9.0 6.5": ["dissectors"], "9.3 12.6 2.6": ["droolworthy"], "1.3 0.6 10.8": ["acupoint"], "12.8 23.8 12.8": ["unloveable"], "2.1 14.5 -3.4": ["reballot"], "-7.8 -1.3 1.9": ["confusional"], "7.4 21.9 8.5": ["neutralino"], "11.8 15.0 6.1": ["smae"], "11.2 19.5 7.1": ["heavilly"], "12.3 10.5 19.3": ["japonicum"], "1.6 6.6 5.7": ["grandfinal"], "5.9 10.0 2.7": ["musicphone"], "-10.2 0.6 7.5": ["turnbacks"], "8.6 4.4 29.7": ["sog"], "4.7 18.2 6.0": ["personalist"], "11.1 4.3 9.4": ["smokeshops"], "4.9 10.7 6.7": ["bargadars"], "15.6 10.8 14.3": ["himbos"], "7.2 3.4 -9.6": ["netowrk"], "2.9 4.4 8.3": ["deinstitutionalized"], "8.6 17.2 13.1": ["shambolically"], "5.6 2.6 5.6": ["educing"], "6.6 27.5 8.1": ["gangsterish"], "12.2 9.3 20.6": ["popu"], "0.9 9.4 1.6": ["argatroban"], "10.8 11.0 23.5": ["hoofin"], "7.9 0.2 -1.0": ["cocreated"], "8.4 7.6 4.7": ["coartem"], "6.7 0.6 9.5": ["disovered"], "4.8 21.6 6.8": ["primitivists"], "5.3 2.8 1.2": ["totalized"], "19.1 3.0 -1.1": ["moden"], "-0.8 22.9 6.2": ["civies"], "9.9 12.4 12.7": ["charlock"], "2.2 7.8 24.0": ["chura"], "3.9 -1.4 11.7": ["choregraphed"], "6.8 8.0 5.6": ["systema"], "-9.5 10.2 -2.1": ["disgree"], "14.2 1.2 9.1": ["intitle"], "8.2 13.1 18.4": ["beguines"], "1.2 11.2 8.5": ["stinkeroo"], "14.0 32.6 4.2": ["cavalries"], "2.0 9.1 10.8": ["nuestras"], "-0.7 9.6 16.5": ["dermatophyte"], "7.9 8.6 7.0": ["retapamulin"], "-3.4 0.7 10.0": ["comanagers"], "3.6 19.3 8.7": ["anoikis"], "10.2 9.1 3.7": ["governme", "yuppification"], "4.7 13.8 9.4": ["cathepsins"], "15.6 25.7 6.6": ["bolshevism"], "1.9 8.1 4.8": ["kipa"], "7.8 6.7 13.2": ["volcanoclastic"], "-0.4 12.7 5.7": ["intoximeter"], "7.2 12.3 0.7": ["eventuall"], "5.0 -5.0 11.0": ["owater"], "12.5 8.2 18.7": ["scal"], "15.0 11.1 34.6": ["rocoto"], "13.8 26.7 16.7": ["restorationists"], "17.1 -1.6 29.0": ["espuma"], "11.6 5.9 8.3": ["downloaden"], "0.3 10.1 9.8": ["explusions"], "0.0 -0.5 14.3": ["pli"], "10.0 -3.8 0.6": ["vandaag"], "31.6 11.2 22.6": ["mouthless"], "15.2 6.7 18.2": ["workshed"], "18.7 16.1 15.4": ["telescopically"], "12.8 0.9 11.6": ["nuove"], "-2.1 8.6 15.1": ["unbridged"], "8.0 0.1 2.1": ["eazybusiness"], "2.3 8.5 13.0": ["nona"], "2.3 5.8 11.3": ["odontologist"], "13.8 12.5 25.6": ["turista"], "-5.9 -2.2 2.6": ["respo"], "2.7 5.4 12.5": ["robotripping"], "-0.8 10.4 4.0": ["andsecurity"], "7.5 0.4 18.6": ["punchboards"], "9.6 7.2 8.3": ["electrothermal"], "11.0 10.7 16.9": ["hwyl"], "5.4 -0.3 2.4": ["retai"], "11.0 -1.4 12.9": ["revitilization"], "19.0 13.5 20.1": ["lemondrop"], "11.8 -2.8 1.6": ["olution"], "15.2 13.1 11.8": ["nowehere"], "10.5 3.6 28.8": ["bagsakan"], "12.7 12.5 28.1": ["tanoaks"], "11.6 5.9 29.4": ["fondu"], "14.3 4.4 19.2": ["crocidolite"], "12.3 4.8 30.8": ["panforte"], "13.8 -3.0 6.3": ["embalms"], "7.0 4.0 4.0": ["thavil"], "-1.1 2.5 11.3": ["diethylpropion"], "-0.6 3.6 6.9": ["delagates"], "10.6 10.9 8.2": ["victoire"], "9.8 18.7 11.7": ["insistency"], "14.9 18.8 7.3": ["forehanded"], "15.7 14.4 3.1": ["crookery"], "16.4 15.9 5.7": ["thesedays"], "1.9 0.0 8.1": ["phlebology"], "13.5 2.1 -0.2": ["icials"], "10.1 7.5 16.9": ["squealy"], "9.4 4.7 11.7": ["stunters"], "11.4 6.2 7.5": ["mflow"], "-6.9 7.8 10.2": ["oildown"], "3.8 14.0 13.0": ["affine"], "-3.7 12.5 5.2": ["undersampling"], "4.8 16.4 11.5": ["excersize"], "5.7 6.5 -2.7": ["mpc"], "-2.7 8.4 10.7": ["tpo"], "7.5 15.1 15.4": ["clownlike"], "10.1 14.5 9.2": ["upbeats"], "15.8 14.6 21.3": ["chuckin"], "11.0 6.6 16.6": ["lithospheric"], "15.8 15.3 32.8": ["pulutan"], "5.7 7.5 10.9": ["grosso"], "11.9 17.8 14.7": ["toomuch"], "-1.7 1.8 -0.0": ["trated"], "-1.7 4.7 15.6": ["antidegradation"], "6.6 13.2 10.7": ["romanticisation"], "4.5 0.9 1.7": ["blee"], "3.9 25.4 22.8": ["greenbugs"], "23.4 1.0 14.2": ["shipmaker"], "-3.1 8.6 3.1": ["roud"], "16.3 7.2 53.3": ["softshells"], "10.1 25.5 -3.7": ["unpatriotically"], "6.7 10.4 14.3": ["sunbake"], "-2.5 -0.0 4.0": ["despedida"], "12.1 35.3 9.5": ["sangar"], "4.2 15.0 13.7": ["colintj"], "-10.1 10.6 4.4": ["doables"], "6.6 14.9 14.2": ["reblog"], "9.6 12.6 18.7": ["rupert"], "7.8 11.9 9.2": ["reuinted"], "8.2 10.9 15.5": ["chypre"], "5.5 17.9 12.9": ["molluscum"], "-0.5 8.7 3.0": ["edgeio"], "5.3 4.5 5.0": ["conso"], "9.6 6.2 16.1": ["tinctured"], "1.5 31.0 14.2": ["intolerantly"], "11.2 10.2 0.5": ["overdelivered"], "10.1 6.5 8.1": ["vitesse"], "0.8 -2.9 15.4": ["pmwith"], "1.1 13.7 5.0": ["embarasses"], "-4.9 5.6 13.3": ["firstcome"], "8.4 -0.4 9.0": ["hieronder"], "13.1 10.8 11.3": ["placein"], "16.7 3.2 14.8": ["crescendoes"], "1.4 1.1 2.5": ["geldanamycin"], "5.3 5.1 4.7": ["postprocessor"], "0.8 -7.9 9.2": ["argo"], "1.9 3.8 10.1": ["drea"], "9.7 16.0 22.8": ["phytoplasma"], "7.8 14.0 14.3": ["manway"], "8.8 13.1 9.0": ["elevons"], "4.0 2.7 13.7": ["ninyong"], "8.6 6.0 0.1": ["isssued"], "-0.4 -3.8 7.7": ["monther"], "1.0 12.2 6.8": ["shona"], "15.0 5.4 22.7": ["marbleizing"], "-4.0 10.6 8.4": ["thermographers"], "1.0 9.5 5.3": ["shelley"], "12.4 5.4 18.1": ["quinto"], "4.5 11.9 8.3": ["oaters"], "8.4 8.6 5.7": ["logorrheic"], "0.7 18.5 18.1": ["torpedoman"], "9.2 8.0 9.3": ["motogp"], "5.0 2.9 -0.5": ["praiseful"], "1.0 21.3 4.4": ["succeeed"], "15.9 5.0 8.2": ["sellings"], "9.1 5.5 10.9": ["doller"], "14.4 30.7 7.2": ["imaginery"], "12.4 9.3 27.2": ["mesias"], "13.1 12.9 23.2": ["parentals"], "13.1 5.5 8.2": ["dunkathon"], "4.6 10.5 9.7": ["neurohormones"], "17.1 12.1 15.1": ["zipless"], "8.0 -4.5 4.2": ["aplications"], "9.6 1.6 26.0": ["fisheree"], "5.7 6.1 14.8": ["wirey"], "6.7 3.5 5.4": ["bookeeping"], "0.8 -8.7 3.4": ["scfd"], "6.3 17.4 3.9": ["slavic"], "-2.8 18.2 8.1": ["relateable"], "2.3 40.3 5.5": ["terorism"], "11.4 17.4 23.6": ["metates"], "-2.2 19.5 15.3": ["mulk"], "8.6 1.5 12.0": ["limberness"], "8.9 11.8 5.7": ["fuerza"], "19.1 4.0 1.1": ["corporatizing"], "4.3 -0.2 -0.5": ["ttc"], "6.6 -2.3 4.0": ["anastrazole"], "1.1 3.4 -0.8": ["misregulated"], "16.8 15.3 11.7": ["jobby"], "1.9 7.5 -8.8": ["saffronised"], "10.3 12.2 35.8": ["humuhumunukunukuapuaa"], "1.9 14.6 -4.4": ["countermands"], "6.3 5.8 13.9": ["megadairy"], "11.9 9.8 17.3": ["dhakis"], "10.4 25.5 -3.4": ["exfiltrating"], "2.4 24.1 6.7": ["almajiris"], "2.1 7.6 1.6": ["assigments"], "11.1 14.2 5.4": ["yippies"], "-8.9 8.3 -1.2": ["reviser"], "16.7 15.5 9.5": ["chatbots"], "2.9 19.7 17.9": ["resentfulness"], "-0.4 -5.8 11.0": ["thirtyninehotel"], "12.0 7.0 24.0": ["stomaches"], "-2.2 3.6 10.4": ["humbucking"], "7.8 4.7 4.7": ["sain"], "1.6 12.8 10.7": ["artemesinin"], "8.1 11.7 17.0": ["westwood"], "0.2 10.3 0.6": ["secondand"], "9.2 9.1 -2.5": ["multifrequency"], "2.8 23.2 11.0": ["dirth"], "8.2 0.1 9.5": ["magento"], "8.1 4.4 5.7": ["vendredi"], "-3.6 -6.2 4.6": ["sors"], "5.3 11.3 6.1": ["immigation"], "3.3 11.0 -1.6": ["artcle"], "17.7 8.4 22.0": ["quaker"], "11.9 3.4 30.6": ["kormas"], "1.3 4.5 7.4": ["accessways"], "4.1 6.8 8.5": ["curtesy"], "10.0 20.1 7.1": ["radiotelephone"], "6.4 2.4 22.5": ["patola"], "12.6 9.1 1.2": ["tipover"], "8.7 9.4 12.6": ["dhurries"], "15.2 -1.1 14.6": ["ctw"], "0.3 9.9 2.8": ["metastability"], "4.5 13.1 15.1": ["haematomas"], "8.7 7.0 26.3": ["sumptous"], "0.7 3.1 0.9": ["saiid"], "6.1 2.9 23.6": ["offstream"], "21.0 10.8 18.0": ["overdecorated"], "12.1 17.5 5.5": ["redistributionism"], "-1.6 10.2 6.2": ["chancier"], "8.0 -4.6 10.0": ["curtainsider"], "2.7 21.4 11.1": ["concidered"], "3.1 13.4 1.8": ["mlas"], "-5.9 -7.0 8.5": ["vate"], "8.3 8.4 1.3": ["enlightener"], "-2.8 -4.5 11.4": ["laun"], "6.0 0.5 8.4": ["lifing"], "-7.0 22.8 2.0": ["thejob"], "2.9 12.8 9.7": ["dravite"], "-3.8 12.3 7.0": ["dexrazoxane"], "2.1 4.4 13.2": ["approps"], "12.1 11.2 22.3": ["thinset"], "20.2 4.5 7.3": ["environmentallyfriendly"], "8.2 8.5 19.0": ["malam"], "5.8 3.6 14.4": ["downtowner"], "10.2 16.5 16.4": ["aish"], "-3.9 2.9 12.7": ["oppor"], "1.8 1.5 8.8": ["ption"], "12.3 3.9 11.7": ["rrific"], "2.5 -0.1 6.4": ["reclocker"], "23.2 8.5 36.1": ["tubeworm"], "9.4 19.4 12.9": ["quickplay"], "18.6 4.1 6.6": ["brokedown"], "5.7 20.3 12.9": ["loooked"], "-1.4 0.4 9.8": ["hvor"], "-0.9 13.5 6.9": ["strating"], "6.1 1.0 14.0": ["paleoenvironmental"], "1.3 6.2 6.6": ["rajiv"], "-4.2 13.1 1.8": ["separability"], "-6.4 5.5 -1.3": ["alhough"], "7.1 17.9 12.3": ["allignment"], "13.1 14.7 24.9": ["boxelder"], "-4.8 9.2 2.8": ["discriminant"], "13.7 14.9 10.1": ["microphysics"], "6.9 6.3 18.0": ["tripel"], "13.2 12.1 8.3": ["cules"], "1.1 1.7 12.4": ["midbody"], "23.9 16.1 13.7": ["pixillated"], "-1.7 9.4 1.5": ["merinews"], "4.8 17.0 -9.2": ["favourate"], "2.7 14.6 10.1": ["landsman"], "-1.2 13.6 3.7": ["cleareyed"], "6.2 2.4 11.0": ["betdirect"], "17.3 12.7 17.9": ["patera"], "-0.4 23.0 8.3": ["imposer"], "14.4 15.0 15.3": ["econocrats"], "5.9 8.1 26.1": ["kachoris"], "18.5 20.9 20.8": ["blammo"], "11.1 1.2 34.0": ["cappicola"], "9.9 12.0 17.6": ["idee"], "1.9 3.4 8.9": ["isoenzymes"], "26.1 21.2 25.0": ["raincloud"], "-10.9 18.0 2.9": ["toknow"], "8.6 11.6 17.4": ["vele"], "8.0 10.0 11.4": ["theodolites"], "2.9 4.1 13.8": ["hexamers"], "9.8 6.4 23.0": ["wiches"], "4.1 19.3 16.0": ["biliousness"], "4.2 15.3 11.9": ["offhandedness"], "4.0 18.3 21.2": ["frostbiting"], "0.8 14.8 2.6": ["laxities"], "15.5 -4.3 30.5": ["fishball"], "-3.4 27.7 12.8": ["conjunctures"], "8.5 8.4 -1.3": ["discplined"], "11.7 -4.4 8.2": ["cetilistat"], "2.5 17.9 10.9": ["nonliteral"], "11.9 15.0 34.0": ["massasauga"], "-4.4 23.6 5.5": ["ansars"], "1.0 6.7 6.0": ["chlordiazepoxide"], "17.1 1.5 11.6": ["accoustics"], "17.8 -7.6 3.4": ["miillion"], "-1.2 -7.2 3.5": ["svs"], "4.9 8.1 15.8": ["georgetown"], "5.6 16.9 9.2": ["overaggressiveness"], "-7.5 -6.6 3.7": ["semesterlong"], "8.1 8.6 4.6": ["natuurlijk"], "3.3 9.6 -0.7": ["scrutinizers"], "5.2 -7.6 -1.9": ["certifed"], "15.8 18.5 19.2": ["skywalker"], "21.9 0.2 39.7": ["miniburgers"], "-4.2 -1.8 -2.1": ["eteamz"], "5.5 7.5 10.2": ["expatriot"], "26.8 26.1 15.7": ["gorgons"], "1.8 9.1 2.3": ["gallup"], "19.7 -5.1 4.4": ["phamaceutical"], "19.2 10.8 13.2": ["gloomsters"], "8.8 16.2 18.1": ["rakiya"], "10.8 8.1 16.2": ["russe"], "-2.6 18.4 9.5": ["misbehaviours"], "2.0 11.2 14.7": ["cementite"], "22.0 10.3 32.8": ["tarpons"], "4.0 11.7 8.9": ["sasman"], "-2.3 0.8 -2.9": ["rasterizers"], "12.3 4.0 3.4": ["shrinkable"], "9.5 3.0 8.2": ["acclerated"], "0.3 -0.1 -4.7": ["ismore"], "13.5 6.3 18.8": ["faires"], "4.8 7.2 -4.2": ["roadable"], "1.5 1.3 10.8": ["grindability"], "14.9 0.3 -3.2": ["comunications"], "11.9 19.3 3.8": ["hijabi"], "6.7 31.0 -6.2": ["disorganizing"], "13.2 3.2 5.3": ["dihydrate"], "-6.0 7.6 -2.0": ["ister"], "8.7 26.8 7.9": ["blaim"], "4.8 12.6 8.9": ["deinterlace"], "4.8 4.4 6.5": ["resolvin"], "2.3 7.2 5.0": ["moldability"], "12.1 18.5 17.1": ["radness"], "6.9 1.2 3.1": ["buysiders"], "3.2 3.9 3.2": ["secondplaced"], "17.1 10.7 19.8": ["ascenders"], "8.4 2.2 -1.4": ["boistrous"], "5.7 10.2 15.9": ["enterotypes"], "6.3 13.7 11.4": ["pradhanavs"], "7.3 3.2 13.1": ["balustrading"], "8.8 20.6 10.5": ["rythem"], "9.0 -1.5 25.5": ["purpleheart"], "-5.4 11.2 4.3": ["slr"], "8.4 17.1 28.5": ["pelage"], "-0.1 -0.8 6.7": ["nonuniversity"], "8.2 9.3 8.2": ["bipole"], "0.4 3.8 18.2": ["matagal"], "-0.5 11.4 6.6": ["disentitle"], "1.5 8.5 -1.5": ["implimenting"], "9.1 1.9 12.1": ["tradicional"], "8.9 6.5 9.4": ["mudpack"], "8.0 -5.6 12.6": ["homegal"], "18.2 12.4 6.7": ["hackability"], "5.3 -3.2 2.0": ["sportwagon"], "9.0 10.2 -3.8": ["pleged"], "0.2 6.3 14.4": ["hodge"], "7.4 12.7 10.8": ["outhomering"], "7.9 17.0 7.1": ["lodestars"], "12.3 -2.6 17.1": ["gunged"], "-2.0 15.8 5.9": ["malperfusion"], "-2.5 15.8 6.6": ["periodisation"], "11.9 7.5 27.8": ["kitfo"], "11.8 3.0 -2.3": ["deblocking"], "19.3 5.0 19.0": ["crispers"], "5.7 2.9 20.7": ["holotype"], "1.6 19.6 8.8": ["susceptable"], "14.0 4.3 16.6": ["lovefeast"], "21.5 -0.1 19.9": ["beanery"], "5.0 -0.6 1.1": ["pmp"], "-3.5 9.4 -0.4": ["exceptionable"], "0.2 16.2 20.1": ["mesic"], "10.7 6.1 12.4": ["folic"], "7.3 26.6 9.9": ["instigative"], "13.3 7.1 12.2": ["pluckiest"], "6.5 2.3 3.5": ["laryngoscopes"], "8.4 5.0 19.8": ["yute"], "4.0 9.2 6.5": ["interproximal"], "-11.5 5.0 -1.3": ["revisers"], "7.6 12.2 8.5": ["overcommercialized"], "9.9 6.7 13.8": ["frontends"], "18.0 12.3 46.0": ["broadbill"], "12.2 5.0 2.1": ["varifocal"], "22.5 19.1 31.0": ["gribble"], "7.4 9.3 7.6": ["ooomph"], "1.5 3.9 9.8": ["additionalinformation"], "5.3 13.2 -2.0": ["mismanagements"], "3.8 2.0 13.6": ["randonee"], "12.0 12.8 -3.3": ["intergrating"], "10.5 7.4 18.8": ["humanure"], "18.5 15.2 15.8": ["ovular"], "8.0 -1.2 0.7": ["offere"], "16.3 4.0 14.7": ["accum"], "21.9 -2.6 19.1": ["tubbed"], "10.7 11.3 14.0": ["woma"], "2.1 5.9 1.4": ["sonographically"], "12.5 17.4 6.6": ["simultanously"], "-2.3 -1.0 14.7": ["linggo"], "12.0 8.3 6.4": ["rotaxanes"], "8.3 4.0 3.7": ["eightysomething"], "8.6 0.8 6.8": ["thosuand"], "0.9 -1.7 3.0": ["regularises"], "-5.4 6.7 12.2": ["associaton"], "12.7 7.3 26.5": ["aviculture"], "5.5 9.6 5.4": ["fotocommunity"], "18.1 9.9 29.7": ["gelatinized"], "11.5 25.9 8.6": ["mistery"], "9.0 13.7 12.1": ["bothies"], "5.0 5.0 23.9": ["bhaat"], "-4.5 -0.2 4.7": ["basestocks"], "4.2 6.0 12.4": ["soapier"], "8.2 2.0 10.5": ["biri"], "3.1 14.4 2.1": ["desynchronized"], "6.7 1.0 11.3": ["bonos"], "12.9 10.2 15.5": ["sepulchers"], "4.6 24.2 10.6": ["trammelled"], "-0.0 -2.3 11.3": ["samping"], "-6.6 23.7 4.7": ["nonconstructive"], "6.3 -2.6 5.4": ["mairie"], "4.7 15.3 16.6": ["cysticercosis"], "9.6 12.8 18.9": ["fakin"], "-5.9 3.9 7.7": ["periarticular"], "7.0 4.3 10.3": ["ffrench"], "-6.6 8.0 7.7": ["humain"], "3.8 26.9 10.4": ["selfdefence"], "2.6 11.8 5.4": ["federalised"], "15.3 9.8 20.9": ["yayo"], "11.5 12.5 11.7": ["detectorists"], "-5.2 -1.4 9.2": ["unicompartmental"], "9.4 7.1 9.2": ["palliated"], "5.0 7.0 11.3": ["pabasa"], "7.0 -1.1 26.6": ["rootcrops"], "6.7 25.0 8.6": ["cognize"], "18.8 12.9 16.9": ["ironsmiths"], "8.4 -3.4 9.1": ["guitarra"], "-3.8 15.6 -2.1": ["unbias"], "15.6 12.5 4.9": ["ringle"], "-1.5 -2.4 -0.0": ["biostability"], "2.0 14.7 2.7": ["precatory"], "-1.3 14.2 5.8": ["photofits"], "6.2 -5.6 4.2": ["samedi"], "2.0 11.9 8.5": ["daid"], "5.6 19.4 -3.9": ["resoundly"], "7.7 5.1 7.1": ["destinational"], "-12.6 6.9 7.9": ["numerated"], "7.2 3.9 10.9": ["polonaises"], "11.1 6.6 2.1": ["deterioriating"], "11.6 5.8 -6.2": ["countercharged"], "7.2 14.2 16.4": ["choppiest"], "4.7 16.7 4.4": ["polesitting"], "9.2 3.1 17.3": ["powderhounds"], "5.9 3.5 10.6": ["bandolero"], "4.2 6.8 6.3": ["fullfillment"], "15.9 0.0 8.5": ["futzed"], "12.2 10.1 4.1": ["feverous"], "11.2 14.8 9.2": ["subsidisers"], "16.8 12.1 3.7": ["latley"], "11.6 8.1 -0.8": ["genericness"], "15.8 9.8 12.3": ["balletically"], "13.6 11.8 15.5": ["vinny"], "-4.8 6.0 3.7": ["textisms"], "8.0 17.5 15.1": ["hoopheads"], "12.8 4.7 17.3": ["microcarriers"], "10.4 14.3 9.0": ["sunglint"], "16.3 12.4 14.6": ["effervesce"], "4.3 9.7 9.5": ["downmix"], "9.1 13.8 2.7": ["obeisant"], "9.3 -1.4 11.0": ["lobal"], "-0.1 14.3 3.3": ["photosensitizers"], "8.9 0.8 5.1": ["construciton"], "6.9 8.6 9.5": ["tpday"], "15.3 17.9 32.7": ["shipworm"], "2.9 1.6 10.6": ["quieren"], "7.2 4.9 18.4": ["cradleboard"], "9.4 3.7 2.5": ["lossof"], "18.7 12.3 16.0": ["chucklesome"], "4.7 7.2 6.4": ["nonretirement"], "6.9 -4.2 2.6": ["workign"], "1.5 11.3 10.1": ["subtance"], "3.3 5.3 11.4": ["maharaj"], "-6.9 4.4 1.5": ["rhabdo"], "4.2 7.7 8.4": ["finda"], "0.8 -8.2 2.4": ["vinvolved"], "22.0 12.5 15.2": ["sawblades"], "3.2 7.2 -3.0": ["lhe"], "1.7 6.6 21.2": ["ecotype"], "3.1 21.5 5.2": ["mear"], "-4.0 14.1 -3.1": ["detailees"], "17.4 2.1 13.7": ["calor"], "18.0 1.5 5.8": ["bape"], "1.8 6.2 15.1": ["agh"], "16.7 15.1 0.1": ["aken"], "-1.5 19.9 12.8": ["mitigative"], "16.6 10.4 18.4": ["octuple"], "0.6 11.4 0.4": ["reemphasised"], "5.6 2.6 -0.6": ["twentyfive"], "23.5 9.7 32.8": ["glops"], "12.2 18.4 17.2": ["thedollar"], "11.5 19.0 12.1": ["numskulls"], "16.1 8.1 18.7": ["unfaded"], "2.6 18.0 10.3": ["quites"], "-4.2 7.1 5.0": ["conversative"], "13.5 -6.9 6.6": ["faciltiy"], "19.5 8.4 23.0": ["goatskins"], "4.5 13.6 12.9": ["mose"], "12.8 4.6 7.6": ["longsleeve"], "12.7 15.8 10.9": ["schticks"], "-0.1 11.5 34.4": ["kaimoana"], "12.9 9.4 16.8": ["brittlebush"], "12.4 2.7 49.7": ["dhufish"], "0.5 4.4 9.6": ["suivi"], "-6.4 1.3 3.1": ["inten"], "9.4 5.9 17.3": ["snowboots"], "9.7 12.7 16.1": ["bacterially"], "4.8 18.0 8.7": ["indigeneity"], "10.6 13.3 18.7": ["crackpipe"], "7.1 8.3 16.0": ["frazier"], "3.5 3.4 7.7": ["skybet"], "19.5 10.4 33.1": ["tideflats"], "14.4 22.2 14.3": ["reeeeally"], "-1.0 19.1 6.8": ["chamcha"], "5.3 -6.7 9.1": ["foodstores"], "3.2 9.3 2.7": ["recountable"], "2.8 0.6 -6.9": ["persuant"], "-0.8 -0.8 3.8": ["chould"], "0.4 1.2 0.8": ["qualfiers"], "-3.4 14.7 6.6": ["underemphasize"], "2.6 1.6 26.4": ["dako"], "14.3 15.6 19.3": ["snn"], "9.7 8.7 16.7": ["unfarmed"], "9.8 12.1 16.8": ["divertingly"], "-1.0 7.1 -0.0": ["proctorial"], "8.9 11.2 12.3": ["tickover"], "9.1 -2.6 -3.7": ["tookover"], "8.5 -4.0 13.6": ["middlings"], "-4.0 -5.5 2.2": ["stru"], "8.1 8.5 16.0": ["lithocap"], "16.9 12.5 2.9": ["geotarget"], "11.7 15.8 21.8": ["ringplane"], "5.3 13.6 1.0": ["recources"], "12.3 2.6 14.4": ["shiploading"], "-0.2 7.0 1.6": ["premotor"], "12.2 10.8 33.7": ["vegtables"], "10.0 4.7 26.3": ["ganaches"], "3.1 2.7 15.8": ["diga"], "0.8 12.1 14.6": ["kalu"], "2.0 -5.1 13.8": ["crche"], "-7.8 11.6 2.3": ["darbars"], "5.4 5.4 20.9": ["flatrolled"], "24.5 12.0 17.4": ["rathskeller"], "5.3 2.6 17.2": ["fia"], "-2.0 14.0 17.8": ["pallida"], "12.9 -0.8 9.3": ["terug"], "17.4 5.8 4.9": ["microfine"], "1.2 -1.3 4.4": ["abusiness"], "4.5 10.8 5.7": ["entertaing"], "16.1 2.7 -3.1": ["bby"], "11.9 3.7 10.9": ["nonstriking"], "2.7 4.9 15.6": ["susunod"], "4.8 12.3 16.5": ["kobudo"], "12.6 10.3 14.5": ["musa"], "14.7 18.7 27.9": ["tamaraw"], "14.2 5.8 26.3": ["dendrobium"], "7.5 0.2 18.1": ["gateless"], "9.2 26.0 22.1": ["kharma"], "10.8 6.0 21.0": ["ponche"], "0.3 -7.9 11.0": ["contrats"], "11.3 3.0 10.6": ["barspin"], "7.5 14.1 23.5": ["sorehead"], "5.3 23.7 11.4": ["unluckiness"], "4.1 13.1 12.9": ["artistjoh"], "3.9 -0.4 5.0": ["anticiapted"], "13.9 -2.7 -0.4": ["milkaholics"], "15.3 22.2 8.6": ["overmighty"], "4.2 -3.4 17.7": ["rui"], "15.3 7.3 11.1": ["overlending"], "10.0 20.9 16.3": ["furriners"], "13.0 14.6 16.2": ["unilluminated"], "10.2 31.5 6.8": ["disinform"], "17.6 13.8 6.8": ["kmart"], "-7.6 22.1 7.9": ["decalogue"], "2.8 -2.7 2.7": ["bookletmaker"], "11.4 26.3 7.8": ["spiritism"], "15.7 4.2 16.9": ["thermohaline"], "9.5 17.0 4.0": ["sweded"], "6.7 13.5 -1.4": ["inefficent"], "16.4 14.5 25.5": ["leashless"], "7.3 10.9 1.5": ["agrieved"], "17.8 8.3 12.1": ["lunger"], "-2.4 9.3 -9.5": ["declanm"], "10.7 0.2 1.8": ["theclub"], "12.2 20.8 13.1": ["dazes"], "14.8 15.8 27.4": ["pomps"], "4.4 6.3 -4.7": ["todaythat"], "14.0 3.6 4.3": ["ternet"], "12.6 -2.3 6.1": ["autum"], "3.0 10.1 10.1": ["desinged"], "6.0 -1.9 9.9": ["cordobas"], "14.6 -0.9 13.2": ["aguinaldo"], "4.0 6.4 9.7": ["hastle"], "-7.4 5.7 6.6": ["homeshoppers"], "0.3 14.9 15.4": ["crusier"], "-2.9 2.2 2.5": ["remise"], "13.8 12.2 13.6": ["kareoke"], "0.3 10.0 14.5": ["excrutiatingly"], "8.2 0.3 3.3": ["urbanscape"], "11.3 1.5 11.8": ["restitched"], "9.4 6.8 -1.7": ["retunes"], "8.1 -1.7 9.6": ["decifit"], "0.7 33.7 4.4": ["militray"], "-1.3 -0.5 11.7": ["exhibitioned"], "12.6 10.2 13.8": ["talkmeister"], "9.1 0.6 9.8": ["consulant"], "-0.3 7.6 10.8": ["ordinals"], "6.1 -8.9 -2.5": ["agnecy"], "3.9 12.2 7.4": ["bizonal"], "14.3 2.9 12.7": ["scoreclock"], "5.7 3.3 18.5": ["anagen"], "6.4 15.5 2.4": ["circumventions"], "5.7 -5.1 4.6": ["theconference"], "-2.5 17.8 5.6": ["oftens"], "15.2 9.2 19.7": ["tuckers"], "9.2 5.1 3.3": ["harding"], "6.3 -4.8 4.9": ["autotest"], "10.9 -0.3 17.4": ["bakeshops"], "6.5 7.9 22.9": ["crutched"], "-4.0 7.8 10.5": ["yaz"], "3.5 10.9 15.7": ["pahk"], "6.6 14.5 7.5": ["bekes"], "3.8 20.7 18.3": ["choicers"], "5.3 2.7 -0.4": ["mumbaitimes"], "14.8 24.1 12.8": ["unrepressed"], "6.1 24.1 2.6": ["extrem"], "-2.3 12.1 8.5": ["etic"], "0.2 7.7 8.9": ["atherothrombotic"], "17.4 2.0 10.8": ["stageside"], "4.8 1.5 0.6": ["acta"], "-2.5 15.1 10.2": ["sherif"], "17.4 28.5 5.9": ["bluecoats"], "2.8 11.4 5.6": ["reinvite"], "1.2 27.9 -3.3": ["fatwahs"], "-3.8 3.3 5.7": ["uniparental"], "11.7 22.9 13.0": ["capoeiristas"], "18.1 15.1 9.5": ["outstretches"], "14.6 2.8 4.2": ["monotube"], "17.9 16.2 19.1": ["ginge"], "10.7 10.1 6.5": ["cuemen"], "14.6 -12.0 -1.2": ["wereldwijde"], "8.8 0.2 9.1": ["andat"], "1.3 10.5 10.0": ["hyperactivated"], "8.1 8.3 2.4": ["girlcott"], "-8.1 7.9 5.2": ["subagent"], "9.7 6.2 30.1": ["zested"], "4.4 11.2 12.3": ["ogogoro"], "5.3 4.1 0.1": ["supercession"], "2.6 11.3 4.9": ["perod"], "18.7 4.6 39.8": ["mornay"], "7.4 11.2 9.5": ["nonjudgmentally"], "-3.4 18.8 1.1": ["sayyid"], "-0.7 10.9 16.1": ["padega"], "12.8 10.2 23.1": ["luncher"], "19.0 6.5 12.1": ["superheats"], "-9.7 16.4 9.5": ["catechize"], "9.6 -1.5 1.2": ["hydromechanical"], "-1.0 6.2 13.6": ["posibleng"], "7.3 6.8 -2.6": ["tolook"], "1.1 17.9 6.9": ["dharm"], "6.4 18.3 21.5": ["paceless"], "5.3 6.6 8.5": ["intactivists"], "16.0 15.9 7.6": ["orgasmatron"], "0.6 3.7 13.1": ["culverted"], "-4.8 9.0 1.3": ["rechartered"], "5.9 -3.7 3.1": ["onr"], "9.4 26.2 14.0": ["redivide"], "4.0 16.3 8.8": ["marshrutka"], "12.9 29.1 4.5": ["deathwish"], "8.3 5.1 13.8": ["antifolk"], "6.6 24.4 10.9": ["submachine"], "9.2 4.7 21.2": ["coralline"], "21.5 2.8 10.1": ["superspike"], "15.7 8.7 3.2": ["socialnetworking"], "9.3 7.8 16.1": ["gravimetry"], "13.2 0.3 11.4": ["irock"], "1.7 23.6 3.6": ["disconfirm"], "2.3 1.1 2.8": ["implementaion"], "11.6 8.6 12.8": ["pinnings"], "4.3 -1.7 17.0": ["rutgers"], "8.3 24.7 12.0": ["stungun"], "6.8 14.4 15.8": ["fruitarian"], "10.4 10.8 19.9": ["euthanasing"], "8.4 -2.3 13.6": ["theamount"], "3.2 25.7 10.5": ["contrariwise"], "23.9 7.4 15.3": ["hubba"], "4.0 8.7 8.3": ["dystonic"], "0.6 4.0 -0.1": ["babyproof"], "6.4 12.1 5.7": ["semiauto"], "7.2 18.9 13.2": ["dpad"], "25.2 6.4 19.2": ["bottlecap"], "14.8 5.1 20.0": ["ultrachic"], "6.7 24.8 20.5": ["asperities"], "12.4 11.3 20.4": ["stillages"], "14.8 10.4 24.0": ["curer"], "4.3 13.8 12.1": ["sqrt"], "9.2 7.1 2.1": ["gamecasts"], "-1.6 11.4 6.6": ["clofazimine"], "20.4 -1.6 5.6": ["industial"], "1.7 -7.7 8.3": ["facilit"], "-1.8 19.7 12.9": ["illed"], "-0.9 -2.3 2.9": ["blogathon"], "10.2 13.5 17.1": ["caulker"], "10.0 4.8 2.2": ["eebee"], "-5.1 19.8 18.3": ["rhizomania"], "3.9 27.9 8.2": ["sahwa"], "9.9 3.8 2.6": ["recasted"], "4.1 16.1 6.9": ["fissions"], "-9.9 2.0 -6.6": ["ustin"], "9.2 10.0 4.6": ["employeees"], "-5.7 8.1 5.6": ["hemichannels"], "6.1 16.7 14.1": ["lugholes"], "8.0 15.1 12.6": ["hames"], "9.2 -7.8 5.8": ["publicsector"], "8.0 4.1 13.7": ["escheats"], "-9.3 -0.1 0.9": ["extn"], "16.1 3.9 8.8": ["verticalisation"], "7.7 17.8 13.2": ["souths"], "3.6 6.0 3.3": ["myelitis"], "16.4 9.0 14.0": ["foxiest"], "9.2 15.1 16.2": ["deepish"], "12.3 8.6 11.1": ["colombian"], "2.1 -1.7 10.3": ["additur"], "11.7 16.0 10.2": ["hangeul"], "9.7 -0.7 11.6": ["greenville"], "2.3 14.2 18.1": ["takehome"], "24.3 6.7 36.5": ["frier"], "11.6 10.7 21.0": ["krunk"], "2.1 14.8 14.3": ["hirsuteness"], "19.5 -8.2 -1.0": ["dataroom"], "11.8 9.8 19.3": ["supergran"], "15.4 21.1 18.1": ["freebooter"], "-11.3 6.5 5.2": ["crossmatch"], "2.6 5.8 15.3": ["madaling"], "18.6 18.1 22.2": ["debeaked"], "13.8 35.1 5.2": ["warefare"], "16.1 0.8 15.1": ["ballpen"], "-0.8 7.4 13.2": ["prorogues"], "12.6 24.9 17.3": ["endospores"], "-7.4 12.2 9.8": ["nonincumbents"], "8.2 2.8 -3.0": ["dataport"], "9.6 9.2 7.8": ["samadhis"], "0.5 -3.9 3.3": ["adjuged"], "7.4 9.8 14.4": ["baan"], "-6.7 -4.4 0.2": ["amoxycillin"], "1.5 28.6 4.0": ["communalized"], "10.7 10.5 15.4": ["murtis"], "15.7 4.8 2.0": ["backdowns"], "-1.3 12.9 17.1": ["tireder"], "10.5 6.4 5.5": ["openhole"], "9.2 20.0 9.1": ["overstretches"], "9.1 17.9 8.9": ["illicits"], "3.5 -2.9 11.1": ["conclu"], "-0.8 11.2 3.8": ["sst"], "9.9 1.4 6.2": ["bonkbuster"], "9.4 34.1 8.3": ["helicoptors"], "9.5 12.5 -0.8": ["forc"], "15.6 5.0 12.5": ["frustum"], "-1.6 -8.3 5.4": ["audioconferences"], "2.7 7.0 9.0": ["iar"], "5.3 9.8 4.7": ["lepton"], "15.9 -4.6 1.0": ["energia"], "7.8 11.4 11.6": ["selectins"], "12.8 20.0 8.4": ["fomites"], "1.0 4.7 14.6": ["pora"], "8.2 -2.6 14.6": ["entomophagy"], "8.5 2.6 11.9": ["rifted"], "6.5 7.3 21.7": ["ovulates"], "-1.2 1.9 5.8": ["ayudar"], "7.6 -2.3 3.5": ["vehz"], "-1.9 14.4 -5.4": ["qualifiable"], "17.0 10.3 33.2": ["tartiflette"], "9.5 -8.1 8.4": ["acm"], "14.0 10.1 15.6": ["bravas"], "4.5 -6.6 3.2": ["whg"], "0.7 20.2 7.0": ["acceptant"], "9.0 12.9 12.3": ["snockered"], "-4.1 0.7 0.7": ["postitions"], "11.6 20.5 6.4": ["finks"], "14.3 14.1 10.1": ["monklike"], "10.3 18.9 8.5": ["multivalency"], "10.6 13.8 17.4": ["ngguanhuah"], "0.2 3.2 12.7": ["footswitchable"], "6.6 13.7 7.6": ["deffinately"], "7.7 9.3 11.9": ["lagna"], "9.6 -3.3 5.1": ["preparators"], "11.8 -2.7 2.5": ["outgrossing"], "8.3 3.0 8.9": ["wordprocessing"], "-5.2 1.7 3.5": ["paginator"], "-5.5 3.4 9.5": ["pseudomorphic"], "14.2 9.6 15.8": ["epicycles"], "6.6 10.8 2.6": ["referer"], "20.4 5.8 41.2": ["deepfried"], "14.0 7.1 15.4": ["milkhouse"], "15.6 6.7 27.6": ["budino"], "6.0 9.0 8.4": ["forcewide"], "20.8 -11.1 4.1": ["emitch"], "14.4 23.1 12.0": ["ressentiment"], "-0.8 25.2 5.9": ["socialiser"], "17.7 13.9 25.9": ["tighted"], "15.4 3.4 40.4": ["potsticker"], "1.5 17.9 4.5": ["sincerly"], "3.1 18.3 10.3": ["antiheroine"], "0.3 9.8 13.1": ["argillization"], "1.8 4.1 5.8": ["thein"], "12.3 18.3 8.6": ["casuing"], "3.1 4.4 23.2": ["nashi"], "25.8 2.3 22.4": ["crystaline"], "13.5 11.4 13.4": ["titantron"], "17.5 11.0 17.8": ["fatsos"], "12.0 22.4 7.8": ["teleoperated"], "2.0 12.8 9.8": ["dhyan"], "8.8 16.5 1.8": ["governemtn"], "3.6 4.2 3.0": ["businesess"], "8.4 -2.1 -5.3": ["annonces"], "1.7 14.2 11.8": ["watchkeepers"], "-5.2 -1.2 14.7": ["isocaloric"], "-11.4 17.2 5.3": ["canditates"], "6.7 9.9 2.0": ["surprisngly"], "1.7 6.7 3.8": ["nestedtypes"], "14.6 4.1 10.4": ["revnue"], "11.0 -2.5 6.8": ["pacakge"], "7.7 8.6 10.0": ["mercuric"], "-0.9 7.6 16.6": ["nawala"], "13.9 4.7 19.0": ["waverunner"], "0.1 8.6 11.8": ["phenanthrene"], "14.6 27.3 15.6": ["spartans"], "7.5 -9.9 0.9": ["microsavings"], "13.1 4.1 12.8": ["dilutable"], "10.0 -0.6 -0.0": ["photgraphs"], "24.6 -4.7 -2.4": ["chmn"], "10.7 2.6 21.6": ["mishti"], "7.6 17.7 17.2": ["alife"], "9.2 12.9 23.0": ["hotspring"], "12.0 4.1 43.1": ["tiradito"], "-0.9 8.7 9.3": ["yehi"], "-5.4 11.6 7.6": ["rist"], "6.6 1.5 12.6": ["prio"], "4.2 0.8 16.8": ["mbf"], "11.2 9.2 19.0": ["harpers"], "3.4 -5.1 37.8": ["shellfisheries"], "7.0 1.9 6.9": ["intaglios"], "3.1 -0.4 3.4": ["roadability"], "3.9 4.0 7.1": ["indicent"], "9.2 21.7 9.1": ["tothem"], "4.7 2.2 8.7": ["calcs"], "-0.6 2.8 10.5": ["footswitches"], "3.4 11.7 4.9": ["hotblooded"], "3.6 12.0 5.1": ["agnosia"], "-3.0 1.4 4.8": ["underwhelmingly"], "7.5 11.8 4.4": ["hireable"], "1.6 3.6 1.9": ["sociologic"], "4.8 5.3 13.2": ["exteme"], "16.9 10.1 -1.5": ["hotdesking"], "6.7 2.7 7.2": ["nanobiotech"], "14.3 23.2 10.9": ["phillumenist"], "4.3 -2.0 13.6": ["bili"], "9.2 3.5 0.7": ["positiv"], "8.9 5.1 19.3": ["carniceria"], "12.3 12.9 19.0": ["downwelling"], "5.9 3.2 3.8": ["persmission"], "12.9 11.2 35.2": ["sauceboat"], "3.5 10.2 9.6": ["perimter"], "8.8 10.6 15.8": ["inicial"], "11.0 8.8 16.8": ["calcifies"], "18.5 0.1 14.0": ["healthfood"], "12.7 14.8 10.3": ["passivating"], "4.2 8.9 13.7": ["advil"], "-2.2 -0.4 2.7": ["seconnd"], "19.8 17.8 10.2": ["alchemized"], "3.8 15.2 8.3": ["eigenvalues"], "10.2 2.2 -2.0": ["thecompletion"], "18.5 1.4 24.1": ["murukku"], "-2.7 4.0 6.9": ["landport"], "5.8 23.7 12.9": ["boyscout"], "9.7 12.7 1.8": ["instaed"], "12.1 1.5 6.2": ["stageful"], "15.1 13.3 19.8": ["goodfella"], "10.4 5.7 1.2": ["timesonline"], "10.9 20.2 0.2": ["regimenting"], "27.6 8.0 26.9": ["spermaceti"], "-3.0 3.1 6.3": ["justed"], "1.9 15.1 1.5": ["combustable"], "0.4 5.5 4.0": ["ypa"], "-5.8 5.3 6.5": ["viraemia"], "11.7 0.5 15.3": ["ultrapremium"], "7.4 17.3 16.3": ["riiiight"], "1.3 3.7 3.5": ["terazosin"], "20.0 8.5 32.6": ["feasters"], "4.1 0.4 15.0": ["microgrants"], "16.5 3.5 16.7": ["decaffeination"], "5.9 10.2 4.7": ["parahydrogen"], "-3.9 10.7 -7.9": ["anamolies"], "7.2 9.3 4.7": ["regorafenib"], "13.3 9.6 11.6": ["spruit"], "11.4 -4.4 1.6": ["expedia"], "6.1 20.4 12.4": ["highnesses"], "-2.7 5.5 7.7": ["exercisability"], "1.5 19.5 5.9": ["dimish"], "10.9 -1.3 4.3": ["tuhl"], "8.4 2.9 2.0": ["tuvo"], "-2.3 5.1 0.8": ["intraperitoneally"], "-4.0 1.4 4.3": ["headgirl"], "-2.8 11.7 4.4": ["disapplication"], "8.7 9.6 13.1": ["thehouse"], "13.0 7.3 21.9": ["chimaera"], "-10.2 10.5 1.2": ["assesing"], "16.2 1.1 29.8": ["cochon"], "14.9 2.0 7.5": ["banglalink"], "17.9 8.0 17.0": ["tanorexia"], "4.9 15.6 8.5": ["itin"], "22.0 -1.9 -5.8": ["subsdiary"], "11.9 7.3 24.4": ["bantengs"], "8.1 9.8 6.2": ["emersed"], "7.6 23.7 -0.1": ["stategies"], "13.2 15.6 3.2": ["adul"], "8.8 7.1 12.5": ["waterbased"], "-0.2 4.2 1.0": ["submitt"], "11.3 7.5 3.8": ["brentuximab"], "12.8 7.1 7.3": ["faz"], "9.7 12.1 4.4": ["eeeee"], "-5.0 6.3 5.3": ["inany"], "11.6 4.2 5.8": ["yesterdat"], "-3.4 18.6 12.1": ["chastize"], "6.2 3.2 5.6": ["ador"], "15.6 7.0 5.8": ["huffer"], "2.6 0.5 7.7": ["documento"], "16.1 8.8 8.1": ["entrepeneurial"], "-2.2 -0.4 -0.0": ["nebulised"], "4.8 7.5 6.0": ["safegaurd"], "14.5 9.7 13.1": ["daly"], "9.4 6.5 10.0": ["euroskepticism"], "14.2 8.4 35.9": ["bulalo"], "-0.3 8.4 14.9": ["bigyan"], "4.5 6.2 19.0": ["trullo"], "29.1 4.7 32.7": ["cocoanut"], "3.6 3.8 -2.1": ["asmany"], "-0.4 7.4 6.5": ["origina"], "1.8 9.7 9.3": ["klaseng"], "8.1 11.3 18.6": ["crossfading"], "8.7 7.7 6.2": ["truimph"], "8.2 9.0 24.0": ["elaichi"], "3.6 -1.6 6.1": ["arraingment"], "-9.0 8.3 -6.7": ["ofinformation"], "5.9 2.9 11.0": ["semanas"], "-4.0 3.9 8.9": ["priya"], "7.1 3.9 0.8": ["glamourisation"], "22.5 20.4 15.8": ["jaybirds"], "5.9 2.2 1.1": ["goalkeper"], "10.1 14.9 16.7": ["superimpositions"], "7.7 2.8 14.0": ["ifanc"], "1.9 8.6 10.7": ["ordinariates"], "6.4 6.8 6.7": ["toallow"], "7.3 8.0 12.2": ["thery"], "7.1 12.1 15.0": ["imag"], "4.6 2.9 -11.5": ["tojoin"], "8.5 19.6 34.2": ["dillweed"], "10.9 10.8 20.9": ["maiz"], "4.2 7.2 6.0": ["microfilaria"], "2.1 -0.8 -0.3": ["patientswith"], "18.2 11.2 6.6": ["neuroprosthetic"], "2.5 10.2 16.2": ["brucei"], "10.3 13.8 4.4": ["ergonomical"], "-3.4 18.9 16.1": ["utu"], "4.4 4.2 0.8": ["gv"], "18.9 6.7 7.9": ["chatroulette"], "-3.5 17.7 6.8": ["baptists"], "-8.0 9.3 6.4": ["headnote"], "4.6 10.0 16.7": ["squeezin"], "-2.8 2.5 2.6": ["admini"], "5.9 19.5 15.3": ["allelopathic"], "13.0 -5.4 8.7": ["laylight"], "-1.3 9.1 7.4": ["bedsharing"], "3.4 13.9 15.6": ["atmoshpere"], "3.6 14.8 -0.0": ["backset"], "7.6 8.2 6.8": ["deskphones"], "4.9 2.1 -2.4": ["propres"], "-0.6 12.1 -3.0": ["inclusivism"], "5.7 17.2 8.7": ["alsatians"], "19.4 17.9 18.4": ["touchin"], "7.8 4.3 2.4": ["prote"], "8.4 6.1 20.2": ["femora"], "8.4 3.0 -6.5": ["picoprojector"], "8.0 14.1 1.7": ["preboot"], "5.5 7.1 11.6": ["kimberly"], "-6.5 6.1 -4.4": ["tabligh"], "2.4 -4.8 6.6": ["demanufacturing"], "13.7 2.6 10.0": ["gowing"], "23.0 19.2 28.0": ["scarers"], "8.4 12.4 10.2": ["agreeability"], "12.0 3.0 7.9": ["bacteriologists"], "25.6 14.1 31.5": ["yolky"], "16.3 3.9 24.0": ["mycoprotein"], "11.6 8.1 32.9": ["chicories"], "13.4 15.1 7.5": ["wandlike"], "-5.5 23.8 -0.1": ["nondeployable"], "7.7 9.8 7.0": ["kennedys"], "23.5 8.4 11.1": ["coporation"], "16.3 6.8 34.4": ["pepperjack"], "4.0 28.3 11.3": ["cocksureness"], "15.8 8.9 2.4": ["telecommunciations"], "-5.0 8.1 1.0": ["questons"], "15.8 4.1 8.9": ["mmf"], "9.0 8.5 9.8": ["darnest"], "7.9 7.3 7.1": ["forthnight"], "13.7 15.7 23.9": ["artiodactyls"], "4.2 18.0 16.0": ["zipcodes"], "25.2 17.5 26.4": ["seahawk"], "14.5 4.0 41.4": ["caperberries"], "8.0 -2.2 16.4": ["gyo"], "-4.5 11.9 -4.0": ["negationist"], "1.2 8.0 -1.9": ["trackrecord"], "10.8 -3.5 18.8": ["bequerels"], "-1.0 12.0 6.9": ["badan"], "5.2 14.3 14.5": ["hoar"], "6.0 4.0 10.8": ["orion"], "2.7 10.2 15.1": ["unexecutable"], "9.4 16.3 14.3": ["deseases"], "17.1 9.2 16.2": ["ditzes"], "5.1 -2.9 -0.9": ["uncollectability"], "6.9 3.3 23.8": ["arneis"], "8.1 9.9 6.2": ["brodcast"], "16.0 13.4 4.0": ["datacomms"], "2.7 7.6 1.5": ["terser"], "0.6 38.6 3.6": ["jihadic"], "8.7 29.3 9.5": ["idot"], "-1.5 9.4 3.4": ["xoxoxo"], "-0.9 14.6 13.7": ["marrage"], "3.6 20.4 8.2": ["cruicial"], "-1.2 14.1 4.6": ["reinvestigations"], "4.6 6.6 -1.0": ["cdrom"], "2.5 -6.1 3.1": ["curre"], "11.7 7.0 13.2": ["droopiness"], "9.7 22.1 15.7": ["cosmogony"], "-5.5 15.2 2.0": ["critise"], "15.6 15.0 10.2": ["finnaly"], "13.4 8.8 -4.1": ["uncoincidentally"], "0.8 17.8 2.9": ["degradingly"], "5.8 2.9 36.9": ["pibil"], "2.1 11.7 8.7": ["unstrapping"], "5.2 6.5 14.1": ["underdo"], "9.4 10.6 9.4": ["organsiers"], "-0.2 5.4 13.3": ["ninang"], "8.4 -11.6 7.2": ["partipate"], "8.8 7.6 14.9": ["flavourants"], "6.7 -5.0 17.8": ["capfuls"], "-4.8 14.5 -4.8": ["iaea"], "7.2 -5.5 26.4": ["fonio"], "14.1 19.0 12.9": ["unbecomingly"], "13.0 5.9 7.0": ["megwatts"], "20.8 6.1 14.9": ["cannonballed"], "-1.0 9.8 -1.0": ["vishwas"], "-0.0 2.3 4.5": ["nanopowder"], "9.5 9.3 14.9": ["brrrrr"], "-6.7 19.9 13.4": ["codels"], "20.4 16.2 28.4": ["dassies"], "5.7 6.3 14.1": ["vetinary"], "15.0 0.4 11.8": ["wachovia"], "14.7 -0.8 34.9": ["porketta"], "7.7 12.5 19.0": ["phelps"], "10.8 5.7 13.1": ["electroforming"], "6.0 6.1 23.0": ["linseeds"], "7.6 11.9 16.6": ["photoperiodic"], "1.4 20.8 4.1": ["diginity"], "2.2 23.3 16.2": ["nuissance"], "3.5 4.6 -1.5": ["andmany"], "32.2 13.2 20.6": ["giganto"], "-2.1 7.9 -7.1": ["innovaphone"], "11.9 1.9 5.8": ["tric"], "7.1 18.8 14.7": ["blockable"], "13.3 19.9 14.7": ["wae"], "9.0 14.9 17.3": ["peaced"], "11.4 12.3 26.2": ["handis"], "5.5 8.4 -1.6": ["demonstates"], "-1.7 -7.6 -2.5": ["aminosalicylates"], "17.1 19.6 4.5": ["hotwiring"], "2.8 1.0 14.3": ["mustardseed"], "-3.9 1.6 -0.1": ["cadette"], "-0.6 7.5 9.7": ["whowill"], "15.0 18.0 4.7": ["everythign"], "5.9 23.4 3.5": ["forign"], "2.5 7.5 7.2": ["brahmacharya"], "-7.7 -2.9 9.6": ["classses"], "16.7 9.3 24.9": ["huskie"], "16.2 7.9 4.1": ["skycrapers"], "12.0 19.7 26.9": ["coasties"], "-3.1 -1.0 10.4": ["mayroong"], "20.9 15.3 4.9": ["jetmakers"], "4.6 13.4 6.0": ["unsportsmanship"], "9.7 -0.8 7.0": ["alllowing"], "17.1 4.2 19.7": ["fanta"], "22.6 -0.2 16.3": ["centi"], "-2.5 1.7 9.2": ["pondage"], "14.4 17.4 15.6": ["enlightenments"], "-8.7 2.7 1.9": ["leukodystrophies"], "-5.5 -8.2 1.0": ["unior"], "12.6 16.7 16.3": ["stoppie"], "8.7 11.2 11.4": ["twelvemonth"], "8.4 17.8 13.8": ["anticipator"], "10.1 8.5 24.5": ["chelada"], "17.1 15.3 24.3": ["southwester"], "20.4 10.7 11.6": ["porkfest"], "0.3 14.2 -1.5": ["harassement"], "-5.1 -2.7 3.9": ["renta"], "4.9 13.6 5.9": ["greenskeeping"], "8.3 11.6 10.4": ["elutes"], "9.6 -6.2 23.7": ["heiferettes"], "1.2 1.3 11.2": ["envirothon"], "3.0 28.7 2.4": ["conspiratorialists"], "10.5 6.4 13.5": ["comodities"], "4.0 17.1 8.6": ["pirith"], "-4.2 0.9 10.4": ["paraformaldehyde"], "8.5 2.9 10.0": ["epilation"], "7.7 -0.8 -0.6": ["hydrail"], "11.9 12.5 5.4": ["cosines"], "-4.5 2.3 -7.0": ["staffmembers"], "0.7 -1.0 -8.4": ["suppported"], "16.0 -0.7 26.1": ["twoonie"], "3.5 3.2 1.3": ["haftime"], "15.1 7.2 4.0": ["ophthalmoscopes"], "-1.0 8.3 20.2": ["ilikemusic"], "-3.1 2.4 22.2": ["ensiling"], "9.3 6.8 16.8": ["petha"], "1.3 -0.8 6.4": ["formance"], "-2.6 -2.4 20.3": ["grapegrower"], "8.6 10.6 1.7": ["andcustomer"], "7.8 1.4 24.5": ["calibrachoa"], "5.1 21.9 7.7": ["unfriendliest"], "1.1 18.8 8.9": ["promicin"], "10.2 8.8 12.6": ["mananged"], "10.3 17.7 7.0": ["multicell"], "13.2 5.3 14.4": ["multitextured"], "12.3 4.1 11.8": ["porticoed"], "0.2 13.0 9.6": ["manav"], "7.4 0.8 11.6": ["hollowbody"], "-10.0 3.1 1.9": ["parishads"], "-4.1 25.0 1.1": ["otu"], "13.8 5.5 10.5": ["whatsisname"], "14.0 -4.9 19.9": ["sorbates"], "8.9 13.0 13.4": ["redistributionists"], "-3.1 15.2 13.3": ["quantifiers"], "3.2 -3.3 0.0": ["salesand"], "-4.2 8.4 4.8": ["esotropia"], "-1.2 0.7 13.1": ["wilmington"], "2.5 19.8 9.3": ["slydial"], "1.5 8.6 5.4": ["theatricalized"], "4.9 16.6 11.7": ["disembodiment"], "8.6 2.1 -1.3": ["fradulently"], "1.6 23.8 3.7": ["hypocritcal"], "12.8 16.9 13.8": ["eventally"], "-2.3 9.4 7.2": ["noncognitive"], "4.1 13.1 9.9": ["dravid"], "6.5 16.6 6.0": ["disordering"], "10.7 1.9 11.9": ["unencapsulated"], "-0.7 0.5 14.8": ["hemoglobinuria"], "7.2 -7.1 1.9": ["enterainment"], "7.2 10.5 12.6": ["ganesh"], "-1.3 1.9 13.8": ["coro"], "15.5 6.0 22.9": ["lassis"], "3.9 14.9 2.1": ["preordain"], "9.2 2.4 12.9": ["returfed"], "-1.3 5.3 9.4": ["microchimerism"], "4.1 7.1 6.7": ["baseketball"], "17.0 12.3 18.5": ["bobbie"], "17.8 9.5 24.4": ["tanbark"], "6.6 16.5 15.9": ["decontaminants"], "-1.3 9.6 -0.4": ["choriocarcinoma"], "9.6 1.0 3.1": ["telehouse"], "-9.2 19.1 6.9": ["shidduchim"], "18.0 10.7 12.6": ["musak"], "-0.5 3.2 -2.3": ["iontophoretic"], "0.3 11.8 7.2": ["uncer"], "20.2 25.9 13.3": ["cybercops"], "-0.2 -0.2 8.4": ["dmv"], "0.5 0.7 5.8": ["talam"], "9.4 18.2 14.3": ["anarchically"], "-1.1 12.9 8.1": ["cryptosystems"], "19.1 12.4 18.0": ["antiquarks"], "11.7 26.8 8.6": ["claustrophic"], "20.6 8.8 24.6": ["cheeze"], "10.7 17.4 23.6": ["allamanda"], "5.0 10.2 4.3": ["hading"], "0.3 19.4 5.7": ["defeate"], "5.1 14.0 8.8": ["maritally"], "3.5 11.2 7.7": ["widespead"], "7.9 27.3 13.2": ["anology"], "-4.1 0.3 3.6": ["fosamprenavir"], "9.3 5.9 18.2": ["minibreaks"], "4.0 13.7 5.5": ["duhhh"], "17.0 -0.6 -0.6": ["soleckshaw"], "11.1 15.7 19.7": ["patu"], "9.0 18.7 6.7": ["charaters"], "1.3 26.9 14.3": ["guildies"], "7.3 12.4 10.9": ["painterliness"], "16.6 1.9 20.8": ["semisoft"], "6.8 4.0 6.3": ["biohydrogen"], "3.8 10.4 12.6": ["industralisation"], "17.6 1.4 31.2": ["oeufs"], "6.8 9.8 19.9": ["puckhead"], "8.1 15.2 4.8": ["nothng"], "-5.9 7.4 -3.2": ["tolds"], "16.3 3.8 7.6": ["aisleways"], "14.8 10.2 10.6": ["manband"], "19.3 1.0 27.9": ["briolette"], "16.8 9.2 36.1": ["chitlin"], "1.5 -1.8 16.7": ["metritis"], "10.9 6.7 17.5": ["susceptor"], "14.8 7.9 10.7": ["macbooks"], "10.3 3.3 -7.4": ["annoncement"], "23.4 11.8 18.7": ["shoofly"], "8.0 4.8 7.3": ["nondepository"], "0.4 1.5 9.7": ["millicuries"], "9.8 11.4 15.4": ["wheal"], "12.0 18.0 16.6": ["uncollared"], "15.8 8.0 1.9": ["enthusastic"], "0.1 -8.1 8.9": ["corticoids"], "-6.2 9.5 -3.3": ["akistan"], "-3.0 6.2 0.8": ["segmentectomy"], "3.1 9.2 8.7": ["soutien"], "4.8 -0.0 9.3": ["satify"], "10.4 9.8 8.7": ["interflow"], "13.4 -0.0 8.4": ["footb"], "6.5 -7.1 -1.9": ["chairmanof"], "6.2 -0.9 3.1": ["hemicycle"], "10.7 9.8 24.0": ["fritillaria"], "-7.1 0.1 5.2": ["vinspired"], "14.8 2.9 5.1": ["postimpressionist"], "17.5 3.0 14.9": ["ecco"], "26.8 18.9 22.4": ["featherlike"], "-7.0 1.4 13.6": ["posisyon"], "2.3 7.8 10.0": ["rapidness"], "15.6 24.6 11.6": ["oubliette"], "0.4 7.1 8.2": ["nonsenior"], "2.5 21.8 0.6": ["baselessness"], "5.0 2.0 6.0": ["cura"], "-1.9 16.2 13.0": ["wantok"], "13.5 24.5 12.5": ["bereted"], "20.7 9.5 14.6": ["adonis"], "-1.1 1.9 14.5": ["neets"], "9.4 7.3 45.2": ["rohu"], "7.7 8.0 15.0": ["sufferin"], "1.0 23.8 13.0": ["overexplain"], "0.3 1.0 8.8": ["pujan"], "13.4 5.0 3.2": ["widgetized"], "9.9 14.4 17.5": ["romantical"], "-4.1 2.9 -1.7": ["frauded"], "5.8 14.1 17.1": ["reloaders"], "11.2 13.0 5.3": ["trusteed"], "18.5 12.7 26.8": ["entrail"], "9.1 4.5 11.0": ["swingweight"], "8.6 14.6 9.0": ["oyu"], "5.0 24.5 11.9": ["consiousness"], "9.9 6.1 8.7": ["claude"], "6.3 18.7 9.2": ["zenlike"], "20.5 14.8 20.5": ["bumbershoot"], "1.6 18.3 1.5": ["convinction"], "0.6 -2.6 9.4": ["urines"], "11.1 4.4 6.2": ["costumiers"], "11.4 8.1 14.3": ["morphogenetic"], "19.0 8.0 20.6": ["lollygaggers"], "15.4 6.6 26.0": ["mandazi"], "4.0 14.2 -7.3": ["responsibe"], "19.4 10.7 25.5": ["totable"], "7.1 8.2 9.8": ["jawn"], "-0.5 6.7 7.0": ["anhidrosis"], "-7.8 7.4 3.3": ["privilages"], "13.7 16.5 22.6": ["subaquatic"], "9.8 9.4 9.0": ["looka"], "10.5 5.9 13.4": ["mountainscapes"], "9.1 1.0 2.2": ["fredthompson"], "16.5 12.7 11.4": ["vegged"], "12.9 -1.8 9.8": ["panelbeating"], "27.7 13.2 11.5": ["megapower"], "6.4 -0.4 5.4": ["radi"], "19.0 7.3 18.2": ["antimusic"], "0.9 11.7 15.8": ["migranes"], "12.9 2.0 32.6": ["lauhala"], "-1.7 10.3 8.3": ["homecourts"], "21.5 3.8 7.5": ["marketeering"], "6.5 7.4 18.0": ["suckout"], "20.2 4.4 10.8": ["vocho"], "8.6 13.5 9.7": ["paperhanger"], "17.8 12.3 21.6": ["backscratchers"], "13.7 4.4 10.2": ["downton"], "17.4 5.3 9.5": ["remianing"], "8.0 9.3 9.2": ["hpv"], "14.7 10.9 4.6": ["hydrino"], "10.9 -1.0 21.0": ["mirabilis"], "7.4 15.7 11.4": ["cosmopolite"], "4.6 3.0 6.2": ["unrenewed"], "12.7 -3.1 16.0": ["tep"], "23.1 4.3 18.8": ["pomaded"], "13.3 18.0 13.9": ["stoppings"], "17.5 10.1 22.1": ["fiddy"], "16.0 11.5 11.3": ["niftiness"], "2.4 39.0 8.0": ["hitpoints"], "13.8 5.6 7.6": ["dobros"], "5.3 10.7 1.3": ["portayal"], "15.1 9.6 7.3": ["overbuilder"], "-0.2 12.8 10.6": ["ruckuses"], "9.7 12.8 14.3": ["magnetosomes"], "6.1 -3.7 14.6": ["punti"], "15.4 -2.7 3.8": ["infoimaging"], "5.0 -3.9 6.3": ["summe"], "0.9 22.1 9.0": ["bodyguarding"], "14.7 5.7 5.4": ["groundworkers"], "1.9 7.9 12.7": ["kapamilya"], "-5.7 18.0 5.5": ["beleve"], "9.0 17.8 -4.7": ["geopositioning"], "3.9 2.9 0.9": ["andservice"], "5.9 3.0 8.3": ["increae"], "9.7 19.3 11.2": ["psychoanalyse"], "-0.0 11.8 18.2": ["tapi"], "8.0 3.9 9.4": ["resortlike"], "1.9 29.9 5.7": ["frailities"], "-1.3 5.3 12.7": ["flushings"], "2.5 3.3 1.7": ["frauding"], "18.1 -1.1 15.6": ["stravaganza"], "21.5 9.7 27.0": ["baldcypress"], "6.2 3.2 9.7": ["pbx"], "9.2 12.5 -0.6": ["ubercool"], "2.6 4.0 14.8": ["superabrasives"], "16.0 29.0 5.8": ["straddler"], "4.7 17.6 1.6": ["srk"], "9.2 10.4 15.7": ["somemore"], "9.3 10.5 10.8": ["diversifieds"], "6.1 22.1 7.8": ["counterreaction"], "-2.2 7.0 4.7": ["ictal"], "12.9 11.8 -2.1": ["asimilar"], "3.8 8.7 6.7": ["eah"], "3.0 5.1 13.8": ["theeconomic"], "6.2 13.5 12.7": ["dout"], "0.6 11.2 2.4": ["slambang"], "7.1 25.9 14.7": ["kamina"], "3.8 15.7 17.1": ["sludging"], "5.1 22.3 24.5": ["nutgrass"], "6.9 6.3 9.3": ["liltingly"], "14.0 7.5 32.2": ["excluders"], "-1.0 9.4 12.1": ["arebased"], "7.9 13.7 16.0": ["celebutards"], "2.1 9.9 8.8": ["unapprehended"], "6.0 9.7 8.4": ["undecillion"], "10.6 12.9 19.1": ["getta"], "7.6 9.5 7.8": ["travailler"], "14.8 -0.9 12.2": ["quizshow"], "12.6 17.5 9.1": ["somepoint"], "3.9 11.1 7.2": ["antirecessionary"], "17.9 6.1 23.9": ["roostertails"], "2.3 17.8 10.0": ["intercommunicate"], "3.9 8.0 -2.2": ["celeberate"], "3.1 15.2 9.8": ["lipreading"], "9.7 8.5 16.1": ["creaseless"], "9.0 5.2 19.2": ["jari"], "5.0 14.3 3.6": ["lockered"], "8.0 7.2 16.5": ["photgrapher"], "5.4 13.6 11.0": ["cya"], "0.9 11.2 12.9": ["galant"], "3.2 9.1 -2.1": ["underusing"], "0.2 7.6 16.2": ["peroxidases"], "10.3 -1.8 17.9": ["skewbald"], "12.4 4.6 19.7": ["recoloring"], "6.5 9.8 5.2": ["pullaway"], "9.2 20.6 7.2": ["thathis"], "5.1 -2.8 9.0": ["tambala"], "9.6 4.2 5.4": ["technican"], "15.4 10.9 31.0": ["mahg"], "16.0 7.8 5.7": ["kluge"], "11.1 16.0 12.1": ["devistation"], "8.7 0.9 39.9": ["mariscos"], "8.7 14.2 8.8": ["relaible"], "27.9 3.8 34.7": ["sicle"], "2.9 19.4 -2.0": ["surived"], "11.0 20.1 14.9": ["chirper"], "4.1 4.8 6.1": ["carveouts"], "13.4 10.6 18.9": ["mamacita"], "6.1 4.9 7.4": ["hamartoma"], "7.0 18.7 7.6": ["kingships"], "7.1 -0.0 0.5": ["dormlike"], "-2.1 -4.3 4.1": ["contributedto"], "0.9 4.6 -2.4": ["berichtet"], "8.9 2.1 6.4": ["comscore"], "0.1 11.2 7.4": ["dini"], "12.9 2.7 -3.4": ["prevously"], "1.9 16.6 4.5": ["scaledown"], "2.3 7.9 2.8": ["talanted"], "12.8 8.6 0.5": ["efficieny"], "3.9 10.6 13.2": ["runestone"], "11.0 20.6 19.5": ["winningugly"], "-1.5 11.7 4.4": ["inabilty"], "19.9 -4.7 0.6": ["postroom"], "4.5 8.5 5.9": ["goff"], "22.1 12.7 20.3": ["bateria"], "7.0 -7.3 26.5": ["osechi"], "8.0 8.7 20.4": ["menhirs"], "6.3 -1.3 3.6": ["productisation"], "9.5 18.5 5.2": ["unuttered"], "3.6 1.3 9.0": ["bowlathon"], "4.0 12.9 13.5": ["halfalogue"], "6.7 16.5 8.1": ["hecticness"], "24.6 12.1 30.1": ["marshmellow"], "3.9 10.1 8.3": ["laudefrom"], "16.1 20.5 13.1": ["mesocyclone"], "11.5 2.2 16.3": ["callbox"], "5.3 8.3 16.8": ["malolactic"], "2.5 18.4 18.0": ["filipinos"], "-4.8 -6.8 1.9": ["subsitutes"], "3.9 14.9 5.7": ["interraction"], "16.9 12.3 6.9": ["redtops"], "3.7 23.4 10.0": ["ethiopian"], "9.6 8.3 7.6": ["ecotowns"], "5.5 14.3 19.5": ["winkie"], "4.6 15.0 12.2": ["pannus"], "21.8 2.9 9.7": ["itcould"], "-8.0 8.3 8.3": ["ineligibilities"], "0.6 15.4 4.1": ["tendulkar"], "0.0 4.8 9.8": ["unembalmed"], "7.4 5.6 19.9": ["gesneriads"], "11.9 -3.6 5.9": ["railside"], "8.4 13.6 19.4": ["spongier"], "17.9 3.2 35.5": ["manapua"], "5.2 0.1 5.7": ["bassplayer"], "14.2 16.5 10.4": ["persiflage"], "7.8 2.7 4.3": ["clickdensity"], "0.8 13.7 12.6": ["muggiest"], "9.7 -5.4 1.4": ["scaleup"], "15.4 -2.0 30.1": ["siomai"], "19.2 7.2 22.0": ["motherglass"], "0.6 17.1 -2.4": ["instrumentalisation"], "18.1 22.6 21.0": ["doonerthesooner"], "15.6 6.9 22.4": ["striata"], "10.7 8.7 24.3": ["gingerbreads"], "18.0 3.8 3.7": ["aquapark"], "12.9 11.5 12.5": ["togheter"], "3.5 3.1 42.1": ["yelloweye"], "-0.4 12.0 16.4": ["unnu"], "23.5 14.8 19.7": ["bashin"], "2.2 12.9 4.3": ["polticial"], "15.4 17.9 22.4": ["mewl"], "13.0 12.1 -2.1": ["vandalises"], "-9.0 5.3 -4.9": ["worte"], "8.0 4.4 0.5": ["selecao"], "18.2 10.5 21.2": ["caracals"], "5.4 1.8 10.8": ["igual"], "11.8 9.0 13.8": ["velomobile"], "0.9 7.1 20.9": ["protocadherin"], "5.5 18.5 5.9": ["seccession"], "-2.0 9.7 7.2": ["toxoid"], "7.9 4.8 4.2": ["herdboy"], "0.3 8.5 3.5": ["exonorees"], "8.7 5.0 -2.7": ["vitory"], "18.6 9.5 14.6": ["sketchings"], "14.0 5.6 5.2": ["urgers"], "13.0 5.0 25.1": ["bakin"], "11.9 4.8 11.3": ["quickstepping"], "-3.0 -3.7 9.3": ["shur"], "13.8 5.7 14.2": ["pillowtop"], "4.1 23.9 8.9": ["homosexualists"], "3.5 3.2 7.7": ["cyberknife"], "1.2 2.0 9.4": ["peridotitic"], "6.9 3.8 16.1": ["cof"], "-0.1 7.9 7.7": ["goalshoot"], "11.8 1.2 10.6": ["inom"], "-6.4 12.9 7.8": ["admendment"], "1.9 3.1 5.1": ["stockdraws"], "6.7 8.5 21.3": ["brak"], "-2.9 18.7 -3.2": ["baised"], "4.0 40.4 7.0": ["delegitimizers"], "7.7 1.5 9.9": ["bugdet"], "-4.3 11.5 1.1": ["effi"], "14.8 2.4 12.1": ["masssive"], "7.5 1.7 6.3": ["ethyleneamines"], "9.6 19.0 -1.2": ["spyplanes"], "14.6 13.8 9.2": ["automaticly"], "13.6 4.3 8.2": ["westsiders"], "-0.8 4.3 9.7": ["sportmen"], "16.1 25.5 -6.7": ["equiping"], "4.0 9.0 -1.2": ["revealation"], "5.5 32.6 6.7": ["jumpmasters"], "-6.5 -3.8 6.8": ["profes"], "5.6 5.3 4.4": ["erate"], "5.3 14.7 10.1": ["theproblem"], "-1.8 2.0 7.9": ["prescaler"], "4.9 5.7 16.2": ["heftiness"], "0.9 16.4 14.6": ["foveal"], "11.0 31.0 7.2": ["conjuration"], "28.5 12.6 31.5": ["uncarved"], "12.2 -1.5 4.7": ["nanomagnetic"], "6.2 13.2 2.6": ["molestor"], "3.6 3.8 4.0": ["diario"], "3.3 5.7 14.2": ["lunate"], "3.9 9.2 19.6": ["epimediums"], "7.9 19.8 15.5": ["whod"], "16.2 6.1 17.0": ["grainery"], "12.3 -4.4 8.4": ["dustrial"], "16.4 23.1 13.3": ["oyibo"], "6.4 4.5 -1.8": ["networkability"], "5.5 6.0 7.4": ["garagiste"], "-2.6 37.9 1.8": ["savageries"], "8.1 16.1 17.3": ["satoyama"], "7.3 13.3 7.1": ["antivaccine"], "0.4 -2.6 11.2": ["centra"], "4.2 8.5 5.6": ["peeth"], "7.2 1.0 0.0": ["informatisation"], "-0.6 10.2 2.8": ["identifiability"], "3.6 14.4 12.5": ["thatyou"], "0.6 5.8 -1.6": ["responsbilities"], "1.3 -3.0 8.2": ["paperworks"], "-1.8 5.8 6.6": ["overprogrammed"], "11.6 2.6 5.7": ["persisent"], "10.6 17.4 16.9": ["dirts"], "4.9 8.3 2.8": ["mrskutcher"], "6.1 12.1 11.3": ["evaporites"], "14.0 -3.8 -2.7": ["basedin"], "7.6 9.0 17.1": ["diuron"], "-2.5 11.2 7.5": ["khandaan"], "16.1 11.4 5.5": ["teabagged"], "23.1 16.7 13.2": ["hopey"], "8.6 9.7 35.3": ["burghul"], "8.1 38.4 3.0": ["mullahocracy"], "19.3 14.2 4.3": ["hypernova"], "0.9 19.3 7.5": ["adl"], "7.4 15.4 9.8": ["tood"], "10.8 17.4 15.7": ["ineffecient"], "12.5 7.6 25.0": ["mitred"], "8.5 1.1 10.7": ["chromo"], "12.6 10.8 10.2": ["talian"], "10.4 -3.6 3.8": ["mercredi"], "2.7 25.6 6.8": ["uncategorically"], "14.5 3.4 6.3": ["interactivities"], "0.1 13.4 8.4": ["esthetical"], "3.8 16.0 12.7": ["againn"], "-6.1 6.6 2.2": ["estabished"], "14.6 21.2 6.4": ["pharmers"], "-4.9 15.7 3.0": ["impermissibility"], "9.3 5.8 9.8": ["holded"], "4.4 14.7 13.8": ["graet"], "13.8 4.5 8.2": ["oopsies"], "2.5 11.0 19.9": ["malaman"], "14.3 14.1 22.5": ["reflexed"], "10.1 3.8 -1.5": ["precontract"], "-0.5 -2.8 11.0": ["ecopark"], "18.4 10.5 9.8": ["moldered"], "-4.1 -2.0 12.9": ["dratshang"], "12.2 2.4 0.3": ["resited"], "6.2 3.0 23.1": ["abbatoirs"], "11.4 4.8 19.2": ["ludes"], "3.0 12.5 7.1": ["confraternities"], "1.9 -7.3 8.5": ["aerobathon"], "-4.9 -4.2 6.0": ["contraindicate"], "7.9 8.1 5.9": ["desai"], "4.2 9.3 11.0": ["jaime"], "7.8 8.2 3.4": ["cyclopentane"], "16.8 12.2 11.2": ["conglomeratic"], "0.6 16.0 8.2": ["nonfamous"], "11.1 18.1 17.0": ["gonnae"], "5.7 4.8 16.1": ["easies"], "1.9 13.2 8.2": ["nonadmitted"], "7.7 17.0 3.5": ["humbuggery"], "8.0 17.1 17.3": ["overplanted"], "7.8 -1.2 22.3": ["rosca"], "-1.4 14.3 2.6": ["sanskriti"], "-2.4 5.6 -2.5": ["nonionic"], "4.1 3.7 4.1": ["jazzlike"], "2.4 14.8 6.6": ["traumatism"], "4.1 11.8 10.3": ["kanwariyas"], "-2.8 1.2 -0.3": ["vihl"], "1.9 0.2 5.5": ["millioncompared"], "11.1 13.7 14.2": ["argillaceous"], "10.4 -3.3 18.6": ["nonfoods"], "-5.7 17.3 7.7": ["prognostically"], "6.8 6.6 5.2": ["moyenne"], "2.5 6.1 4.9": ["pyeloplasty"], "2.7 6.1 6.0": ["sxith"], "1.3 14.4 8.2": ["disfluencies"], "2.2 -3.3 6.9": ["princeton"], "18.3 10.6 21.5": ["whittler"], "12.2 7.3 20.7": ["formosa"], "5.9 29.2 9.2": ["bloddy"], "1.4 15.2 15.8": ["mudik"], "4.9 5.6 8.8": ["butthat"], "15.4 3.7 28.0": ["halupki"], "25.9 10.7 10.2": ["superdense"], "14.4 -4.8 16.4": ["fayres"], "-3.1 17.6 10.8": ["unhopeful"], "11.2 17.7 16.3": ["lowlying"], "13.0 17.4 18.4": ["archie"], "-3.0 8.6 1.4": ["channelopathy"], "11.5 11.7 11.9": ["treemaps"], "15.4 11.4 9.8": ["illict"], "1.4 12.0 12.5": ["absolutions"], "15.2 11.5 16.6": ["andas"], "18.6 29.2 11.9": ["beheader"], "7.2 14.9 11.4": ["limpest"], "-3.0 8.9 0.2": ["tenecteplase"], "7.4 10.1 15.9": ["mayaman"], "3.0 3.0 -6.7": ["intrumental"], "5.2 15.7 9.8": ["gradational"], "15.1 5.5 17.0": ["waify"], "-5.9 14.3 3.9": ["professorate"], "2.7 16.6 5.1": ["dominat"], "14.3 6.4 28.8": ["cattleya"], "17.0 7.5 11.6": ["hotfoots"], "18.6 11.4 28.5": ["stickily"], "13.3 13.2 10.5": ["ledged"], "-1.3 2.4 3.4": ["depr"], "2.4 1.8 14.0": ["tingnan"], "7.3 18.3 10.8": ["ulitmate"], "7.5 8.8 5.0": ["plb"], "15.4 7.1 41.5": ["amandine"], "6.7 11.2 16.6": ["whitman"], "2.4 10.3 22.0": ["cultivatable"], "5.1 7.0 -5.7": ["oustings"], "4.3 7.1 8.9": ["spelers"], "14.3 13.0 14.6": ["jibbed"], "-2.0 4.5 9.7": ["replatted"], "7.8 3.9 -3.9": ["instituion"], "7.9 15.0 16.9": ["neighors"], "6.4 7.7 21.1": ["matzohs"], "9.8 24.5 16.2": ["repugnantly"], "7.9 6.6 4.5": ["logfiles"], "7.0 15.3 17.6": ["bastnaesite"], "8.3 6.1 6.3": ["motocycles"], "20.2 11.1 31.9": ["moulted"], "17.1 20.2 38.5": ["nutmeat"], "3.0 10.1 15.4": ["bhaang"], "-5.5 2.1 5.7": ["compromis"], "11.7 26.8 8.3": ["counterplots"], "6.2 11.2 23.2": ["owling"], "15.9 13.2 12.2": ["nanochannel"], "4.9 5.2 22.2": ["trish"], "13.8 2.5 19.2": ["hardstone"], "1.5 11.2 0.1": ["considerers"], "-4.8 8.9 -2.1": ["sufffered"], "0.2 10.5 9.2": ["pakka"], "4.9 20.1 10.2": ["byroads"], "4.4 4.1 5.8": ["phonebank"], "0.5 15.5 15.9": ["desquamation"], "22.9 14.2 9.6": ["treadles"], "7.4 16.1 5.7": ["fedral"], "3.6 12.9 3.0": ["wantsto"], "11.0 27.5 14.3": ["duppies"], "6.3 10.1 22.2": ["lilium"], "18.6 13.3 22.2": ["downto"], "-3.9 7.4 10.5": ["rason"], "7.2 -0.1 14.3": ["oneonta"], "5.5 8.1 12.9": ["chhe"], "4.9 -0.2 4.9": ["kov"], "8.0 -10.0 8.1": ["onth"], "23.1 8.5 27.8": ["bezoar"], "7.1 9.0 14.8": ["tincidunt"], "-4.7 -1.8 7.0": ["phosphorothioate"], "6.5 17.4 11.9": ["kushti"], "4.1 6.1 -11.0": ["telegate"], "13.4 18.3 7.9": ["thesite"], "18.0 -1.6 10.5": ["worldfamous"], "7.1 -2.2 15.2": ["municipio"], "23.2 4.6 7.3": ["biggests"], "2.1 8.2 4.6": ["civilrights"], "16.4 20.0 11.3": ["tokoloshe"], "4.9 15.1 6.9": ["inhalator"], "6.3 22.3 12.2": ["mechanoreceptors"], "0.9 1.7 7.6": ["mrad"], "15.5 10.6 16.8": ["slabby"], "-1.5 -1.4 9.0": ["jasperoids"], "9.1 8.6 21.9": ["powdercoating"], "11.1 7.3 17.9": ["graystone"], "-0.5 16.9 4.9": ["radicality"], "0.5 3.5 9.5": ["defibrotide"], "1.6 -2.0 10.1": ["mayores"], "3.3 17.3 11.8": ["vectorial"], "-5.8 13.6 -1.3": ["slanderously"], "22.3 5.2 14.0": ["quadrilles"], "16.1 6.1 -6.0": ["inititive"], "-4.0 1.3 4.2": ["unmatured"], "28.1 1.7 5.9": ["manufactureres"], "17.6 -1.0 -4.0": ["serices"], "8.6 11.6 5.1": ["centimetric"], "6.8 4.5 4.3": ["looki"], "8.2 8.3 4.5": ["lamproite"], "3.9 8.0 7.3": ["monocoques"], "1.2 9.3 19.6": ["skyer"], "0.2 31.5 9.1": ["causalties"], "14.5 22.4 24.2": ["moais"], "12.9 3.9 13.7": ["pastille"], "11.5 14.4 5.2": ["hassaid"], "3.3 6.2 1.8": ["ultracompacts"], "7.3 9.6 6.5": ["dispensible"], "6.5 -3.7 0.4": ["bpo"], "-4.4 4.5 2.8": ["footcandles"], "9.3 -0.4 3.6": ["eleveneleven"], "7.3 12.6 26.4": ["overcapitalization"], "11.1 8.1 9.2": ["luce"], "14.3 8.5 1.4": ["whille"], "9.7 4.2 21.8": ["woodball"], "-2.4 13.9 9.5": ["warne"], "25.9 5.0 23.3": ["diabolos"], "0.9 16.3 -0.2": ["fieldable"], "1.0 -2.1 7.0": ["caes"], "14.5 34.4 12.8": ["undeath"], "9.3 2.3 13.5": ["benzol"], "11.8 9.0 18.2": ["dimorphic"], "4.2 2.7 2.6": ["tenurial"], "20.9 14.5 12.3": ["sleak"], "5.3 5.8 8.1": ["arteriovenous"], "-6.3 11.0 -5.8": ["shlichim"], "18.8 9.2 11.9": ["frazzles"], "-9.6 -4.5 -2.8": ["additiona"], "11.4 15.8 13.7": ["xterm"], "9.8 13.0 13.6": ["eartip"], "5.5 3.6 -0.6": ["bioseparation"], "1.8 21.4 -3.1": ["uncredible"], "7.9 1.6 9.8": ["printemps"], "1.8 12.8 2.2": ["committement"], "10.4 19.1 15.0": ["zab"], "11.7 25.3 13.3": ["indiviuals"], "1.8 7.9 10.4": ["aniridia"], "3.8 4.4 7.3": ["conseguir"], "3.4 11.8 22.4": ["angelonias"], "4.6 -8.8 -8.4": ["revaled"], "10.3 0.9 15.6": ["underwired"], "4.6 16.5 3.9": ["bispecific"], "13.8 5.6 14.5": ["stickpin"], "12.5 18.1 5.3": ["foresaken"], "5.9 24.3 1.8": ["calmative"], "3.2 6.1 21.1": ["saging"], "-1.7 -2.7 0.7": ["bgng"], "2.2 -0.7 12.6": ["puntersrealm"], "5.1 0.5 0.5": ["newsaper"], "-2.2 -7.0 -3.5": ["telehealthcare"], "8.2 0.9 7.5": ["servcie"], "-0.3 2.2 14.8": ["alluvials"], "4.1 5.9 7.0": ["positivists"], "18.3 6.7 20.9": ["flicky"], "8.5 -2.9 -0.8": ["pdt"], "5.6 6.2 19.6": ["duckets"], "-5.2 16.2 7.5": ["mathmatically"], "3.5 20.0 9.8": ["triplane"], "16.1 10.1 8.8": ["portakabin"], "14.3 8.0 50.3": ["morwong"], "0.9 1.3 -0.2": ["nable"], "11.6 14.5 11.3": ["balkiness"], "17.7 -2.3 16.5": ["frappucinos"], "3.9 10.9 11.9": ["carminative"], "-5.9 -6.9 1.6": ["photorejuvenation"], "0.0 7.5 7.7": ["zinda"], "21.5 10.0 17.6": ["monumentalism"], "7.8 -0.0 11.5": ["interdental"], "8.5 24.4 7.2": ["unhorse"], "19.1 6.0 3.9": ["univeral"], "20.2 4.2 22.9": ["cafetiere"], "-5.2 -6.7 5.7": ["xperience"], "7.4 -5.8 11.6": ["strippermobile"], "-5.2 3.7 4.2": ["anteversion"], "7.0 16.0 0.1": ["islamabad"], "13.0 9.6 11.2": ["nekked"], "15.8 8.6 21.7": ["liquidise"], "6.1 5.6 6.9": ["metabonomics"], "5.0 6.6 17.1": ["bughouse"], "18.4 2.1 8.0": ["jemmied"], "-3.5 7.6 1.9": ["counteraffidavit"], "2.6 8.3 2.7": ["localisations"], "10.8 17.8 6.4": ["unfamiliarly"], "1.1 10.3 7.9": ["everybodyfields"], "12.6 28.4 21.7": ["smited"], "1.7 12.3 8.9": ["topoisomerases"], "5.1 7.2 14.3": ["agrichar"], "3.9 6.2 14.6": ["guaracha"], "15.0 19.0 5.6": ["outide"], "18.7 6.6 19.2": ["nonallergenic"], "5.9 6.8 6.5": ["peptibody"], "4.4 2.0 3.4": ["hessnatur"], "10.9 7.4 10.2": ["deflashing"], "3.3 9.0 11.9": ["cohabitors"], "1.3 30.2 8.9": ["opponants"], "1.9 3.1 1.3": ["ulation"], "13.8 23.9 15.6": ["flickerings"], "8.3 15.8 18.1": ["charactered"], "6.2 6.8 12.3": ["greywackes"], "3.1 0.2 7.3": ["kyoto"], "-2.3 5.0 11.4": ["gaged"], "9.6 -0.1 15.0": ["ysgolion"], "4.7 12.2 10.6": ["nervily"], "-4.0 10.5 13.4": ["definintely"], "-5.5 12.6 2.6": ["detrained"], "15.7 4.3 15.7": ["flacons"], "3.3 13.1 15.0": ["devitalized"], "-5.9 9.5 7.2": ["hermeticity"], "12.9 7.7 10.2": ["pixi"], "8.0 5.5 7.7": ["itsproducts"], "17.8 -2.9 5.8": ["dolalrs"], "11.2 18.9 14.4": ["blither"], "4.6 4.8 9.3": ["outyears"], "7.1 -10.8 13.7": ["isomalt"], "12.3 5.1 6.9": ["payg"], "20.8 16.2 24.7": ["longways"], "4.9 14.8 4.9": ["differrent"], "19.4 3.8 4.9": ["crashin"], "16.6 30.4 9.3": ["vacillator"], "11.4 1.6 -0.9": ["ageed"], "2.5 1.5 -1.0": ["aspergers"], "7.9 7.1 24.6": ["posset"], "20.2 19.6 27.6": ["macrofauna"], "3.7 7.6 21.4": ["doro"], "6.6 8.4 1.2": ["nanostrings"], "0.6 18.1 10.7": ["intensly"], "4.1 4.5 10.8": ["biphenyl"], "3.7 2.7 8.4": ["tazia"], "13.7 6.8 9.7": ["quadro"], "-2.0 14.3 2.9": ["neces"], "5.7 1.7 10.9": ["identicals"], "15.7 11.2 -3.7": ["amove"], "10.8 3.9 -3.3": ["bluemedia"], "8.5 18.0 21.6": ["overhandling"], "8.3 2.7 12.0": ["angeles"], "17.6 15.9 15.4": ["clippy"], "12.2 17.3 10.9": ["borning"], "-2.7 3.3 8.8": ["emer"], "-6.3 2.2 8.6": ["preschooling"], "6.2 5.8 12.4": ["mattifying"], "4.1 0.2 8.4": ["annuation"], "2.8 11.0 10.4": ["mujhse"], "17.6 17.2 8.6": ["backbiters"], "4.3 5.0 2.7": ["candelas"], "13.0 1.9 14.2": ["coiffing"], "6.5 8.6 23.5": ["goosegrass"], "-6.0 8.7 4.7": ["radion"], "9.8 4.0 20.5": ["pareos"], "4.6 0.4 10.3": ["ailleurs"], "3.8 37.2 1.2": ["idf"], "3.1 21.6 10.8": ["exagerating"], "1.0 5.2 2.4": ["subutex"], "4.8 3.7 7.5": ["incluye"], "3.1 9.5 4.9": ["ehe"], "14.3 11.4 15.1": ["itr"], "11.3 14.6 2.3": ["stiring"], "6.6 7.5 14.2": ["mausam"], "4.1 5.3 3.4": ["repartitioned"], "3.9 6.6 8.3": ["programmmes"], "12.3 2.1 17.8": ["redeposits"], "2.9 12.7 9.6": ["sanskar"], "9.4 12.8 23.0": ["driftless"], "11.9 -0.7 5.8": ["milagros"], "1.7 5.7 14.4": ["tieghu"], "16.3 3.1 36.1": ["kue"], "2.8 33.2 3.0": ["gendarmery"], "-0.3 -1.5 2.3": ["nadroparin"], "19.2 20.7 13.0": ["vapourized"], "7.7 18.2 0.2": ["obasanjo"], "-2.0 9.6 11.2": ["degs"], "17.3 17.3 12.3": ["pleanty"], "4.7 15.0 2.6": ["engram"], "5.7 3.4 15.8": ["corseting"], "10.7 8.7 13.9": ["huo"], "13.4 3.4 16.7": ["seagate"], "2.3 6.7 6.0": ["periocular"], "6.3 11.4 7.4": ["leff"], "-6.0 15.0 8.9": ["twelveth"], "10.8 2.4 10.8": ["kikoi"], "-1.7 -0.3 12.9": ["nondemented"], "9.7 13.3 10.5": ["fmttm"], "7.6 8.4 28.2": ["polynyas"], "7.2 22.5 5.4": ["postbellum"], "5.4 17.2 18.5": ["hangun"], "0.7 8.4 16.2": ["iverson"], "17.8 26.7 22.3": ["boogyman"], "7.2 8.8 15.1": ["dolostone"], "6.2 19.4 9.5": ["resecured"], "14.8 6.5 16.3": ["gooiest"], "7.0 -0.7 11.6": ["dyeable"], "12.6 20.3 7.3": ["persia"], "15.7 6.7 12.8": ["binbag"], "26.2 2.8 25.7": ["laquered"], "7.2 5.0 5.2": ["reshelved"], "7.1 -1.2 4.9": ["onemonth"], "8.9 5.0 16.3": ["anjali"], "0.1 16.4 20.2": ["mycoplasmas"], "14.9 0.5 19.3": ["ruou"], "4.1 8.8 7.8": ["arimidex"], "7.9 12.2 18.3": ["fisk"], "16.2 8.7 13.5": ["abashedly"], "16.3 6.3 5.5": ["eqipment"], "-1.2 6.1 23.5": ["cutblocks"], "22.2 2.7 7.4": ["wunderkinder"], "3.3 6.0 0.7": ["fenestrated"], "4.3 6.6 2.3": ["invovling"], "6.7 4.1 14.4": ["minglers"], "15.7 8.5 7.0": ["eclat"], "8.0 14.7 10.4": ["okadas"], "18.4 27.4 9.6": ["shadowlands"], "9.8 7.4 6.3": ["pointings"], "2.4 7.0 3.1": ["exiciting"], "6.2 9.0 10.0": ["whatshername"], "16.1 -3.9 5.0": ["dancercise"], "10.6 16.6 9.1": ["snidey"], "1.5 1.7 1.1": ["photograher"], "9.0 1.0 1.8": ["willmake"], "21.7 4.6 16.3": ["allnight"], "-4.6 -1.4 -0.3": ["manadatory"], "0.8 6.5 9.5": ["jeanne"], "15.7 4.8 11.8": ["zazz"], "-6.0 -4.1 0.8": ["qualifiy"], "3.4 4.4 10.2": ["acci"], "6.0 0.4 12.3": ["kont"], "14.5 15.8 26.6": ["cockler"], "21.1 -1.0 5.7": ["includinga"], "-0.1 11.1 6.8": ["chemoresistant"], "16.8 6.4 24.5": ["splish"], "2.3 -4.4 3.2": ["theproposed"], "3.7 -0.9 8.0": ["offcampus"], "13.0 6.2 10.2": ["microcomponents"], "1.4 15.7 3.2": ["textualism"], "4.3 1.9 -1.4": ["tranported"], "12.0 0.5 4.6": ["phthalocyanine"], "4.5 6.2 7.9": ["thecompanies"], "12.0 13.3 20.3": ["hokeyness"], "16.0 10.6 3.7": ["bistability"], "1.6 12.2 9.4": ["pursuiting"], "9.6 8.6 18.5": ["natual"], "-2.3 21.4 7.1": ["atimes"], "10.6 -9.0 1.9": ["mercial"], "16.1 12.8 10.5": ["boxen"], "-1.7 4.8 10.9": ["domiciliaries"], "9.5 2.0 10.5": ["osteoprotegerin"], "-0.7 3.7 1.0": ["consti"], "0.3 12.0 11.6": ["sakhi"], "13.3 5.2 11.7": ["alufoil"], "0.4 5.4 16.0": ["mahina"], "10.7 9.5 10.0": ["efi"], "1.5 6.3 -4.3": ["trasfer"], "-4.1 12.5 6.8": ["anisometropia"], "9.5 5.0 9.8": ["lapdesk"], "11.1 6.2 11.7": ["polymerizes"], "6.4 6.1 8.5": ["caldwell"], "14.1 24.7 1.1": ["immenent"], "4.8 18.4 14.8": ["uhmm"], "20.8 29.9 15.1": ["mantling"], "-7.0 10.8 -0.5": ["transdenominational"], "5.9 25.9 12.6": ["sidequest"], "20.4 18.9 39.5": ["blennies"], "3.5 17.3 13.6": ["wussified"], "0.8 16.5 14.4": ["beri"], "2.5 5.1 0.9": ["manging"], "22.8 7.5 12.7": ["frother"], "-3.2 0.9 1.8": ["whereunder"], "4.6 6.0 9.4": ["schuhe"], "2.5 14.6 16.6": ["misfeeds"], "6.5 8.4 12.3": ["chuckhole"], "-3.6 3.4 4.9": ["recoupments"], "2.0 -6.5 0.6": ["nihk"], "7.0 6.0 4.9": ["filme"], "6.2 8.2 21.5": ["eppy"], "11.0 12.2 32.7": ["queenie"], "9.2 10.5 6.5": ["misattribute"], "13.3 12.9 14.3": ["quik"], "3.1 14.2 3.5": ["progressors"], "-0.9 3.4 7.6": ["tenotomy"], "7.6 17.8 5.8": ["irlandes"], "12.0 0.3 0.5": ["purch"], "1.7 3.4 13.7": ["remai"], "6.8 8.1 17.0": ["montuno"], "15.2 -4.5 -0.8": ["copany"], "18.4 11.3 36.2": ["souvlakia"], "9.9 2.3 14.1": ["eui"], "-3.0 -4.9 6.2": ["reinitiation"], "3.6 -4.8 3.1": ["accruement"], "18.7 2.7 16.8": ["suma"], "17.0 14.1 7.7": ["unstitch"], "2.4 22.9 5.2": ["theorization"], "4.3 14.5 10.0": ["whatthe"], "10.7 -4.3 10.9": ["millioin"], "10.4 4.7 10.4": ["gamerpics"], "1.5 5.6 15.1": ["gumawa"], "9.3 8.9 14.7": ["cyanoacrylates"], "7.9 12.7 8.6": ["okapis"], "10.0 18.9 7.5": ["unconsenting"], "10.2 8.6 26.0": ["lories"], "14.2 19.2 3.1": ["hoonage"], "1.6 33.4 -2.1": ["martydom"], "5.7 10.8 23.1": ["grandmamma"], "9.5 3.8 11.9": ["nanocluster"], "-4.7 11.8 3.4": ["naat"], "1.0 3.9 15.1": ["limang"], "-7.3 4.4 9.3": ["swered"], "6.4 14.8 14.9": ["redhanded"], "6.6 4.5 16.7": ["officewear"], "10.6 -1.0 17.7": ["liftable"], "2.3 -5.4 -0.3": ["arthroscopies"], "-4.2 17.0 1.4": ["ashraf"], "-3.9 3.1 8.8": ["hydroxocobalamin"], "1.9 2.3 9.7": ["lightpaths"], "6.1 13.3 5.6": ["nver"], "3.7 12.5 -3.4": ["icontrol"], "2.6 1.5 -1.2": ["seedoflife"], "5.0 -0.9 14.4": ["bandeaus"], "18.6 6.3 24.9": ["agastache"], "1.8 11.2 1.0": ["outdrink"], "3.5 -1.4 6.5": ["interleaves"], "5.1 1.9 5.4": ["archdeacons"], "5.0 5.7 10.7": ["razzled"], "4.7 2.0 23.8": ["chakki"], "4.7 10.0 5.1": ["badwill"], "4.5 18.0 9.0": ["sendin"], "7.4 24.7 8.0": ["teapartiers"], "20.1 7.0 5.5": ["teledildonics"], "2.1 12.8 7.6": ["wg"], "11.7 16.7 8.0": ["brillaint"], "12.8 6.2 7.2": ["goodyear"], "6.4 14.8 9.6": ["smartasses"], "11.3 10.6 11.3": ["oxes"], "15.1 9.1 11.8": ["candlemakers"], "11.4 29.1 27.9": ["jackpine"], "-3.7 -0.3 0.3": ["reinstatment"], "22.1 18.5 11.3": ["squirrelling"], "7.9 11.1 22.3": ["malar"], "7.7 10.0 9.1": ["twangier"], "-4.8 15.5 -6.0": ["tenent"], "9.0 17.0 1.0": ["miskicks"], "4.2 1.8 10.2": ["superstocks"], "3.0 -5.7 9.6": ["izer"], "1.1 -8.5 12.0": ["sesssions"], "-3.8 2.4 2.1": ["nosology"], "-2.3 3.0 21.1": ["kiwifruits"], "6.7 5.6 8.2": ["yyy"], "2.6 25.2 -6.4": ["harkis"], "-0.1 8.7 3.0": ["nobis"], "4.5 12.4 8.4": ["consesus"], "9.3 5.0 6.3": ["dopehead"], "3.4 16.3 1.2": ["invovlement"], "0.9 11.4 5.5": ["manodharma"], "18.7 11.2 11.8": ["yesss"], "9.3 4.9 8.0": ["safflowers"], "19.4 11.6 14.5": ["unanimated"], "17.9 4.5 5.3": ["relighted"], "1.1 6.6 -2.1": ["ety"], "16.6 20.7 21.4": ["tempation"], "11.9 19.5 19.5": ["pickable"], "1.5 13.9 9.8": ["expostulation"], "7.1 18.1 2.0": ["reconcilers"], "8.5 4.0 8.8": ["equpment"], "3.3 6.3 6.7": ["huit"], "15.2 6.0 1.0": ["chromatographs"], "24.4 14.3 15.7": ["shinnied"], "3.7 1.8 -2.0": ["annexin"], "16.1 13.9 16.6": ["ozzie"], "-2.3 4.2 0.3": ["recipent"], "6.6 -1.7 8.7": ["percentfrom"], "14.4 5.5 7.4": ["mophun"], "-2.3 9.1 2.0": ["vars"], "-8.9 12.5 2.8": ["ficers"], "13.7 2.5 13.7": ["subindustries"], "7.0 9.9 17.5": ["mato"], "4.2 31.2 9.1": ["uncheckable"], "5.3 7.9 3.0": ["foreveradog"], "5.9 -4.3 13.3": ["behr"], "5.1 0.1 6.7": ["educare"], "1.5 15.5 0.1": ["nonfactual"], "5.1 8.6 14.6": ["dulhan"], "-0.9 3.5 5.5": ["yesterdy"], "20.9 12.6 21.4": ["cliffsides"], "3.9 6.1 8.6": ["extrusive"], "4.8 -3.3 6.1": ["fle"], "1.3 -0.3 11.4": ["slopitch"], "18.3 6.3 19.3": ["unglamorously"], "18.0 17.0 42.2": ["stickbait"], "4.8 14.8 15.4": ["myiasis"], "10.5 26.3 8.4": ["westernizing"], "12.9 17.6 16.2": ["knifemen"], "10.7 16.6 10.3": ["plyers"], "5.3 10.8 3.8": ["wantedto"], "5.4 12.9 12.1": ["tragedians"], "-4.6 8.6 7.5": ["coprolalia"], "10.4 -1.6 21.4": ["kwai"], "0.2 7.7 5.8": ["chronical"], "-5.2 11.4 0.3": ["kurultai"], "-9.4 3.9 3.1": ["postprocedure"], "7.6 6.9 2.3": ["therecent"], "6.9 4.3 17.0": ["signora"], "7.1 14.3 7.3": ["glenjohnson"], "-2.7 14.5 10.9": ["bachche"], "16.5 11.1 15.0": ["yardangs"], "-8.6 0.1 -0.9": ["recontract"], "1.0 11.2 17.0": ["lams"], "9.8 20.3 16.0": ["bipods"], "10.9 6.6 11.2": ["hotbutton"], "16.4 -3.8 0.6": ["relists"], "11.3 0.7 30.6": ["deseed"], "-6.1 -0.6 3.3": ["fallot"], "22.3 12.2 7.1": ["sweding"], "18.2 15.7 10.2": ["fumigates"], "5.7 14.5 13.6": ["astros"], "11.1 19.3 16.4": ["misfolds"], "10.9 1.6 9.4": ["producto"], "3.4 2.1 6.3": ["lignins"], "9.9 2.5 22.6": ["daytripper"], "0.6 6.1 14.6": ["istorya"], "6.7 12.9 -2.1": ["deine"], "10.9 5.0 18.1": ["swee"], "3.8 29.8 4.5": ["cowardness"], "8.4 6.3 10.2": ["tournamant"], "14.3 3.9 2.5": ["andhigh"], "17.4 9.0 27.1": ["concolor"], "4.6 0.7 -9.9": ["reportedthat"], "4.0 11.9 6.3": ["pleomorphic"], "10.4 10.6 34.3": ["koftas"], "-13.1 7.3 -1.9": ["imphal"], "11.6 -3.4 6.4": ["rentboy"], "10.6 -0.8 16.6": ["crias"], "12.8 19.4 15.2": ["overeem"], "2.6 20.6 11.5": ["outgroups"], "3.9 8.5 5.8": ["nvr"], "6.2 17.1 14.2": ["allusiveness"], "2.9 15.2 18.0": ["amavasya"], "-2.5 2.5 11.1": ["levator"], "-2.7 5.9 13.7": ["dysglycemia"], "7.1 10.8 9.9": ["superatom"], "7.0 8.1 14.5": ["baratis"], "10.9 11.0 4.3": ["transversing"], "5.0 13.4 2.5": ["delphic"], "2.6 0.0 15.4": ["dihydrocodeinone"], "3.3 11.5 14.1": ["bbroman"], "6.9 13.5 3.2": ["chaffeur"], "10.6 15.9 16.5": ["pleeeease"], "-7.7 5.0 6.3": ["mesotheliomas"], "10.3 19.3 7.0": ["nonconducting"], "6.7 4.4 15.8": ["runin"], "19.7 9.4 20.6": ["olivewood"], "-1.6 7.3 5.5": ["reiner"], "7.8 1.8 14.0": ["ofd"], "9.8 3.0 10.3": ["echeck"], "-7.7 -1.9 3.9": ["pretransplant"], "9.1 -2.7 4.3": ["technologique"], "-0.8 8.4 8.3": ["tomarrow"], "-0.9 -2.0 -7.5": ["followd"], "2.0 17.2 19.8": ["sidestroke"], "2.6 2.9 9.0": ["prioryear"], "-1.2 25.4 -0.5": ["decolonise"], "-1.1 0.1 10.0": ["goodtoknow"], "9.6 -1.3 40.0": ["ledgered"], "6.1 4.0 31.4": ["depuration"], "7.8 11.9 18.4": ["kii"], "2.5 -1.9 -0.3": ["secondhighest"], "4.4 11.0 10.1": ["iniesta"], "9.4 2.8 8.1": ["razr"], "0.0 0.5 9.7": ["condensable"], "4.9 23.2 15.2": ["betimes"], "10.8 11.7 12.9": ["pointofview"], "5.0 9.3 5.0": ["matman"], "13.2 7.3 22.0": ["comber"], "11.7 1.4 12.0": ["awwws"], "4.8 11.4 3.6": ["throroughly"], "17.4 7.9 29.8": ["santoku"], "6.3 -1.8 8.1": ["oned"], "5.3 3.9 7.5": ["discoid"], "1.6 10.4 -7.4": ["returnto"], "5.2 10.1 10.4": ["bhfuil"], "0.9 14.8 13.7": ["mahimo"], "-8.9 2.3 2.7": ["nft"], "8.2 16.3 21.2": ["depressor"], "9.9 22.1 10.6": ["buddhi"], "-3.8 0.7 13.2": ["kandi"], "10.5 9.8 30.2": ["clethra"], "8.0 10.4 16.0": ["redepositing"], "-8.5 9.6 5.6": ["differenct"], "-6.2 -6.8 -2.9": ["idential"], "24.6 11.7 33.9": ["butterballs"], "8.5 0.6 9.8": ["lahk"], "6.3 5.6 11.5": ["fack"], "10.9 16.1 16.1": ["radians"], "1.6 9.4 11.1": ["minu"], "17.6 20.5 17.4": ["bandwagoner"], "8.4 4.7 18.4": ["fsa"], "7.3 5.4 8.0": ["proteostasis", "omnes"], "3.9 18.0 17.3": ["tapback"], "9.2 12.3 1.3": ["disuade"], "-1.7 5.4 4.7": ["fineable"], "3.9 -1.0 11.7": ["reborrow"], "2.9 -2.6 3.9": ["publiques"], "-0.7 6.3 1.6": ["solithromycin"], "14.8 13.5 17.6": ["pices"], "25.0 9.8 17.1": ["encrusts"], "17.2 5.1 13.0": ["shoppertainment"], "5.5 0.1 -3.0": ["taxexempt"], "9.7 32.8 8.3": ["harmads"], "10.6 16.1 9.2": ["bedwetter"], "-2.1 -1.9 14.1": ["ruminal"], "7.4 7.5 7.3": ["prolog"], "0.2 4.9 14.5": ["simbahan"], "10.0 -3.2 11.5": ["onselling"], "12.1 1.5 0.4": ["parenterals"], "5.5 -0.7 4.3": ["schoolrecord"], "15.0 20.0 22.2": ["asps"], "7.9 26.6 7.0": ["disinfo"], "0.8 14.6 8.2": ["leiomyoma"], "7.7 10.4 15.2": ["ellagitannins"], "15.8 20.8 9.3": ["emporer"], "18.3 14.2 9.8": ["enchanters"], "-4.8 30.6 3.8": ["proclaimers"], "-2.9 4.4 3.9": ["wininng"], "3.5 11.1 12.4": ["hawak"], "10.9 10.2 20.4": ["germander"], "11.2 9.6 9.1": ["besonders"], "2.5 15.2 3.3": ["firstchoice"], "5.6 26.8 8.3": ["avoide"], "18.6 5.9 11.4": ["oilprices"], "14.8 1.4 2.8": ["softare"], "8.5 3.8 6.2": ["sportsbikes"], "3.5 12.6 12.4": ["antrum"], "7.8 13.6 17.7": ["opala"], "7.0 3.6 27.1": ["muscats"], "17.1 3.3 13.7": ["requred"], "-0.6 15.0 9.4": ["voilent"], "-6.3 10.7 6.8": ["refrac"], "4.8 25.2 11.2": ["experiencer"], "4.6 -4.1 -3.4": ["magazin"], "7.5 20.2 7.8": ["crazyness"], "3.6 17.8 13.0": ["obstreperousness"], "14.3 5.8 20.4": ["cenospheres"], "10.3 1.9 4.7": ["althoug"], "-5.2 3.1 5.0": ["rehabilitiation"], "4.2 -7.9 -3.1": ["ewallet"], "5.2 13.3 5.5": ["circularize"], "2.8 22.4 -6.6": ["sympathic"], "7.5 6.9 27.1": ["vindaloos"], "-1.6 4.6 7.9": ["outrights"], "-9.4 5.7 4.5": ["repolls"], "3.9 -7.0 18.0": ["calendered"], "2.1 9.3 10.2": ["observantly"], "-1.7 11.8 3.9": ["resdients"], "10.6 12.6 3.6": ["expressional"], "6.5 15.7 6.5": ["bossom"], "7.1 11.9 10.9": ["resh"], "13.8 1.9 4.7": ["companywith"], "16.3 15.6 18.2": ["galumph"], "4.8 -8.6 4.4": ["crc"], "4.2 5.4 -1.5": ["specifially"], "6.6 0.9 2.8": ["logiciels"], "5.8 0.8 12.2": ["tonewoods"], "11.1 6.3 12.5": ["extemporized"], "7.8 10.9 10.3": ["formof"], "18.5 4.7 5.1": ["tooters"], "15.2 24.8 14.6": ["peckerwood"], "10.3 7.4 13.8": ["wus"], "1.8 30.3 4.1": ["tamilians"], "5.3 2.5 22.8": ["tarik"], "4.1 20.5 2.8": ["offlimits"], "1.1 11.2 4.1": ["deviser"], "2.2 8.7 3.9": ["titillations"], "8.4 7.6 1.7": ["comforable"], "15.6 3.5 12.6": ["traditionaly"], "2.8 11.2 8.4": ["reinflation"], "9.7 11.4 7.0": ["hygrometers"], "15.8 6.4 33.8": ["kimbap"], "0.1 25.0 6.4": ["grundnorm"], "7.4 9.9 19.9": ["roostertail"], "0.2 12.9 7.6": ["maunderings"], "6.1 10.8 5.0": ["dalethorn"], "1.1 11.9 0.5": ["oesophagectomies"], "-2.3 5.0 6.8": ["crimewatch"], "-2.6 14.4 3.4": ["constition"], "-0.9 8.4 6.7": ["thirdbase"], "5.6 6.6 8.1": ["straigth"], "16.9 11.1 14.0": ["cadjan"], "7.6 9.4 12.8": ["abuelo"], "9.4 25.6 2.6": ["offfensive"], "8.4 5.6 8.9": ["moodle"], "15.0 5.3 14.2": ["esophagi"], "2.4 5.7 -4.3": ["bundesliga"], "9.9 22.0 9.4": ["cougher"], "-10.0 -8.4 -8.6": ["fowarded"], "7.6 14.2 30.2": ["algaes"], "0.4 7.9 21.0": ["kiteboards"], "2.9 18.7 8.3": ["protracts"], "-0.3 3.0 19.3": ["arborescens"], "-1.2 -0.9 8.5": ["pph"], "4.4 10.3 12.5": ["skatearound"], "2.5 9.1 9.4": ["samalizumab"], "12.1 4.1 10.1": ["framerail"], "-0.3 9.2 12.6": ["sulphidized"], "14.5 9.7 11.6": ["anodization"], "11.1 28.1 15.0": ["metroid"], "-2.4 -4.0 6.8": ["parkrun"], "-8.0 -0.0 0.8": ["presentors"], "7.3 6.1 16.5": ["stepwork"], "9.5 4.8 8.9": ["efecto"], "4.5 3.9 10.7": ["neededto"], "11.6 13.6 15.8": ["papz"], "-2.3 1.9 15.8": ["dida"], "6.4 13.0 4.1": ["tribeswoman"], "6.6 6.5 -1.7": ["lixiviation"], "1.9 11.0 13.8": ["olsen"], "1.5 9.9 -5.6": ["procuration"], "2.8 15.1 4.4": ["rightof"], "13.9 10.2 22.8": ["joss"], "-0.8 1.5 8.3": ["ginawang"], "10.7 8.0 24.2": ["microelements"], "2.9 6.2 13.6": ["condensin"], "2.5 8.3 -1.6": ["tke"], "11.7 20.8 12.8": ["underconfident"], "10.7 11.5 16.1": ["bubkes"], "8.0 1.0 8.0": ["demin"], "15.9 2.2 17.8": ["clydesdale"], "10.1 10.0 14.6": ["lving"], "11.4 13.5 10.6": ["skydeck"], "8.7 8.8 27.5": ["fuul"], "29.8 8.6 22.6": ["tilter"], "18.6 13.5 10.9": ["blogoshere"], "22.1 6.7 11.5": ["flyposters"], "7.4 4.4 4.2": ["copperfasten"], "2.3 -0.7 4.4": ["advalorem"], "-2.0 10.5 3.9": ["tryptase"], "-1.6 7.8 3.9": ["transvenous"], "-0.6 -2.2 1.7": ["nounce"], "3.9 1.4 2.1": ["uncollateralised"], "9.0 4.0 22.8": ["pino"], "2.8 4.0 -3.9": ["torial"], "19.5 18.8 11.2": ["munificently"], "19.2 3.2 13.1": ["aficianado"], "6.8 1.6 0.2": ["lised"], "0.2 14.0 0.4": ["fraternalism"], "-6.2 -14.5 4.9": ["yeasr"], "0.8 1.2 3.5": ["hablan"], "13.5 3.8 3.0": ["openreach"], "11.8 15.1 20.0": ["zoogoers"], "5.7 10.8 17.6": ["electroshocked"], "7.7 3.4 2.8": ["eservices"], "1.9 4.9 1.0": ["acertain"], "1.3 8.2 -1.4": ["praesidium"], "23.9 6.3 9.9": ["theprice"], "8.8 4.9 10.1": ["leucoderma"], "8.6 24.0 12.8": ["royalism"], "18.4 15.7 6.7": ["trashers"], "6.8 -3.7 2.5": ["quoteboard"], "8.0 0.4 10.4": ["weks"], "2.6 5.1 5.6": ["nonscience"], "7.8 0.4 7.3": ["unforecast"], "12.3 5.3 2.1": ["compagnie"], "14.8 10.1 7.9": ["ordinateur"], "18.0 5.8 20.0": ["traditonally"], "11.0 -2.0 -1.2": ["toacquire"], "15.2 -0.8 -0.7": ["dvision"], "7.8 9.9 15.4": ["rescure"], "1.0 6.5 11.1": ["graphique"], "10.1 25.0 5.0": ["collectivizing"], "-7.2 6.4 11.0": ["fullbore"], "-0.1 2.8 11.5": ["paceway"], "10.8 11.6 20.0": ["tailbones"], "-11.0 6.3 5.0": ["muzakarah"], "7.4 9.6 5.4": ["nega"], "7.6 16.1 7.3": ["bludgeonings"], "12.2 8.5 14.5": ["fatto"], "3.7 9.9 14.7": ["bebopper"], "7.7 -1.1 15.3": ["wilde"], "-1.3 2.6 12.6": ["bading"], "14.2 11.8 27.4": ["vermicast"], "8.2 -5.5 17.0": ["texels"], "14.8 5.3 37.6": ["spiedini"], "-2.8 -1.2 7.9": ["photochemicals"], "6.8 2.4 11.4": ["parksrec"], "10.4 9.6 1.2": ["subfund"], "-0.3 9.6 7.0": ["requir"], "14.5 16.7 8.7": ["softheaded"], "11.7 22.8 6.8": ["highscores"], "12.6 25.7 5.6": ["patriarchic"], "3.7 5.3 6.3": ["gradebooks"], "8.8 2.5 1.5": ["zet"], "10.4 10.9 5.3": ["satcoms"], "17.0 20.0 10.8": ["gamespace"], "13.0 1.9 10.7": ["colophon"], "20.9 17.7 7.9": ["betterer"], "-2.9 11.0 7.4": ["raphe"], "-1.5 14.0 7.6": ["anosognosia"], "11.0 5.7 13.8": ["alternativa"], "7.3 -2.5 13.3": ["bangor"], "10.0 11.2 11.7": ["daoine"], "8.4 2.1 -4.4": ["investiment"], "6.7 13.4 2.2": ["idw"], "20.4 8.7 18.2": ["ballcock"], "8.2 5.7 13.7": ["adozen"], "-1.2 4.4 7.7": ["pyrargyrite"], "1.6 15.5 7.5": ["centreforward"], "-2.8 2.1 10.1": ["rce"], "8.1 19.6 0.8": ["copycatted"], "12.1 15.3 12.5": ["superness"], "13.4 -0.8 13.3": ["acidisation"], "5.4 22.9 10.4": ["leaguemates"], "20.4 7.8 16.3": ["sheeny"], "1.9 -1.7 8.0": ["performingarts"], "5.0 7.2 17.3": ["kaal"], "8.5 7.3 8.0": ["gogos"], "7.8 24.8 15.7": ["noontide"], "23.4 29.2 10.6": ["unescapable"], "10.9 17.0 14.7": ["punx"], "0.1 9.3 13.1": ["ganglioside"], "19.7 -1.0 12.2": ["compostible"], "11.1 19.5 11.2": ["ovas"], "1.7 -3.9 0.7": ["kft"], "12.2 7.6 14.3": ["leftfooted"], "5.3 -0.9 2.4": ["itemises"], "6.4 -4.4 15.1": ["surchage"], "-3.4 0.0 7.1": ["pseudoaneurysms"], "14.6 9.3 10.2": ["microbead"], "-4.2 18.2 3.1": ["moser"], "5.0 -4.9 15.0": ["colli"], "6.8 7.1 8.4": ["matriach"], "9.6 24.7 17.1": ["unwomanly"], "5.6 3.3 11.7": ["lyophilised"], "4.3 1.8 8.3": ["ltrs"], "1.6 9.3 3.2": ["potentiometric"], "-3.4 6.6 5.5": ["fout"], "10.5 0.5 0.2": ["overviewing"], "6.0 2.0 2.2": ["ralfinamide"], "19.9 1.6 34.0": ["aquafarms"], "18.1 13.6 15.9": ["acroos"], "5.5 15.4 9.3": ["isness"], "6.7 10.8 15.9": ["cronkiter"], "-2.5 12.0 3.3": ["yare"], "9.2 7.6 5.0": ["mirada"], "9.2 6.1 13.9": ["busers"], "11.5 19.6 6.1": ["mkdir"], "19.7 9.4 6.0": ["micrographic"], "-0.3 20.2 4.1": ["takbir"], "9.3 15.5 16.8": ["divalike"], "1.8 14.8 0.1": ["artcile"], "2.0 6.4 -2.5": ["purpotedly"], "5.5 9.0 2.9": ["ourproducts"], "5.6 -0.1 5.5": ["dck"], "-6.9 21.7 2.9": ["responsibilies"], "14.7 -4.5 14.5": ["lustrously"], "9.8 5.6 30.2": ["golabki"], "3.9 0.8 13.1": ["tlaa"], "22.8 4.9 15.0": ["jewellike"], "4.0 0.5 20.2": ["twelfths"], "5.5 1.4 14.9": ["canterbury"], "7.5 7.2 2.5": ["demostrates"], "2.8 12.8 18.6": ["pythium"], "5.6 4.0 8.7": ["santeros"], "7.4 -1.2 10.7": ["chalan"], "4.8 5.3 9.6": ["verschiedenen"], "3.9 -2.8 -1.2": ["diethyl"], "5.3 1.4 15.1": ["sofi"], "15.7 1.3 14.3": ["dogwalk"], "9.4 -2.6 8.8": ["jac"], "6.5 -2.8 10.0": ["taxfilers"], "7.3 11.2 7.0": ["ataxic"], "16.4 7.1 29.6": ["cocido"], "7.5 6.4 22.8": ["monofin"], "4.3 21.6 10.4": ["cfengine"], "2.8 7.1 19.0": ["lagering"], "1.4 12.2 10.1": ["hammie"], "1.5 16.8 14.7": ["iven"], "5.2 3.5 9.4": ["envir"], "10.7 10.1 16.9": ["vollyball"], "13.0 22.1 8.6": ["repealers"], "6.5 14.4 23.1": ["afikoman"], "5.3 -1.7 9.6": ["railport"], "4.8 19.3 6.3": ["technogenic"], "-14.0 6.8 7.0": ["retainability"], "17.3 9.0 13.6": ["leadlight"], "9.0 7.5 12.8": ["oftime"], "6.9 12.9 16.1": ["nadu"], "-2.6 12.7 0.4": ["appologized"], "22.0 4.5 18.1": ["enormo"], "-10.5 -4.7 3.3": ["eighthgraders"], "1.1 7.0 15.8": ["fivesomes"], "16.4 22.6 21.8": ["wisterias"], "2.6 3.2 14.7": ["serai"], "-0.7 6.0 12.6": ["bisulfite"], "5.6 18.8 5.0": ["tandava"], "15.9 18.5 7.2": ["favourtie"], "20.0 8.3 4.0": ["hypesters"], "3.2 15.3 6.2": ["methodolgy"], "8.2 -2.3 26.9": ["cotija"], "-0.6 -2.0 10.0": ["opportun"], "26.0 9.5 34.4": ["rhinocerous"], "2.0 8.2 3.1": ["demerol"], "-7.4 1.5 4.2": ["ttorney"], "-2.6 10.5 23.0": ["everbearing"], "8.4 0.7 12.2": ["gallu"], "10.0 19.9 13.0": ["paganistic"], "5.6 6.1 4.6": ["imagist"], "3.9 15.1 8.6": ["unbuckles"], "9.4 9.3 14.3": ["lousing"], "6.8 16.0 20.9": ["frostbites"], "8.3 1.7 16.3": ["quietish"], "16.4 3.7 -0.1": ["tersest"], "10.6 4.1 14.4": ["rocketmail"], "1.5 15.3 15.6": ["gatti"], "8.6 15.3 -1.4": ["guman"], "17.0 11.8 21.0": ["submergible"], "12.3 8.9 42.0": ["cooters"], "2.0 -1.4 2.9": ["augural"], "3.4 11.9 18.3": ["thumris"], "3.1 2.4 -3.4": ["dimeglumine"], "15.2 5.6 8.4": ["eeek"], "14.5 9.2 17.9": ["rivermen"], "9.7 0.9 21.9": ["zep"], "7.6 28.5 3.8": ["phantasy"], "8.8 43.1 4.7": ["airforces"], "29.1 12.8 25.8": ["tossin"], "9.8 17.9 10.1": ["cumbrous"], "0.9 9.0 4.8": ["methandrostenolone"], "6.3 24.9 5.8": ["factionist"], "-0.0 7.5 9.3": ["shaan"], "9.3 -1.6 13.4": ["utili"], "14.9 9.4 13.0": ["tattooes"], "14.7 25.2 16.7": ["avalance"], "3.3 9.7 16.7": ["keratoses"], "-5.1 12.6 5.1": ["pyridostigmine"], "12.9 6.5 9.8": ["nanoholes"], "11.7 13.7 2.6": ["caterwauled"], "5.9 12.3 12.8": ["kalari"], "-7.0 5.0 -0.8": ["finsihing"], "8.7 9.7 10.4": ["archaelogist"], "13.2 -2.1 15.3": ["crem"], "3.5 -1.8 -3.4": ["parner"], "4.1 3.6 6.8": ["athlets"], "10.5 16.4 2.1": ["goldbug"], "-2.4 7.1 3.2": ["fufilling"], "4.4 -3.6 20.9": ["ribfest"], "1.3 20.6 15.9": ["dillema"], "15.4 10.8 13.2": ["cinemagoing"], "18.7 12.2 41.3": ["loaches"], "12.8 20.1 18.0": ["rotweiller"], "19.4 19.1 13.6": ["megaclubs"], "-1.9 -4.7 -1.4": ["tated"], "15.2 16.2 12.2": ["variey"], "2.1 -2.4 4.0": ["chairholders"], "2.2 24.2 7.4": ["occident"], "6.5 6.3 19.5": ["colar"], "12.1 19.7 13.1": ["lingeringly"], "5.4 14.2 7.0": ["laners"], "-0.4 10.8 13.3": ["subramanian"], "6.9 3.0 10.6": ["subito"], "6.4 10.9 6.6": ["knowlingly"], "5.2 11.6 11.0": ["fuckable"], "7.2 6.0 15.6": ["hyperglycaemic"], "-2.8 2.1 3.3": ["workingwoman"], "0.1 14.0 1.7": ["dysrhythmias"], "8.2 2.2 29.4": ["cebiche"], "9.6 12.7 16.4": ["flavinoids"], "6.1 2.9 8.7": ["blogcast"], "18.5 9.0 11.4": ["flythrough"], "6.6 14.2 17.8": ["stevem"], "3.0 5.8 10.6": ["reassayed"], "3.4 35.5 -2.0": ["terrrorists"], "10.7 33.8 7.8": ["chekists"], "0.5 3.9 -1.4": ["derestricted"], "5.2 16.8 5.9": ["disfunctionality"], "7.2 8.4 4.3": ["falderal"], "21.6 9.2 12.1": ["remeasuring"], "26.3 18.5 28.8": ["whapping"], "7.2 9.2 14.3": ["drumless"], "20.9 22.2 12.7": ["webslinging"], "2.8 7.0 1.9": ["awell"], "5.5 5.8 8.9": ["reblocking"], "4.8 7.8 3.2": ["worrysome"], "15.5 15.4 7.1": ["headress"], "9.8 4.4 2.7": ["oup"], "5.9 8.4 10.1": ["backlanes"], "6.1 0.9 15.5": ["capriccio"], "5.0 10.9 11.4": ["norcalnick"], "0.5 11.0 12.8": ["iscsi"], "3.0 7.5 3.6": ["rehost"], "-4.0 4.6 -2.8": ["uality"], "7.7 9.0 36.6": ["thosai"], "16.2 7.5 10.1": ["isango"], "6.5 -2.7 4.2": ["baratos"], "2.1 19.2 9.2": ["weit"], "-3.2 16.3 6.6": ["inforced"], "13.2 11.6 -0.9": ["busniess"], "-0.5 9.8 11.3": ["achha"], "3.1 7.9 8.5": ["acinar"], "17.8 9.3 31.0": ["springform"], "-7.0 15.7 3.8": ["unordained"], "15.6 8.5 6.6": ["sportback"], "-2.3 -5.1 8.0": ["upt"], "2.3 5.9 11.9": ["neighborhod"], "4.2 6.3 -3.2": ["realtions"], "10.9 17.0 7.4": ["peopole"], "22.0 -0.1 19.9": ["dryosaurus"], "10.6 13.7 3.6": ["rasterized"], "1.8 8.1 12.4": ["chlorophyllin"], "11.7 7.7 29.4": ["gnatcatchers"], "16.4 4.4 13.0": ["apsara"], "11.0 19.5 15.1": ["chowderheads"], "-0.8 -3.9 1.1": ["preemployment"], "2.1 8.6 3.9": ["psl"], "12.8 8.0 23.0": ["itty"], "5.8 1.3 19.9": ["feldspars"], "8.5 6.2 13.6": ["diin"], "-10.5 1.8 3.4": ["sasid"], "2.9 1.7 4.4": ["ksnnithya"], "16.1 31.4 7.7": ["mly"], "6.1 9.8 11.7": ["umd"], "16.6 32.1 10.6": ["overdogs"], "19.8 10.6 33.8": ["noddies"], "13.4 -3.3 -4.4": ["addidas"], "1.0 18.4 19.2": ["seabag"], "13.0 9.4 0.9": ["strongrooms"], "6.2 9.5 9.2": ["bootmakers"], "5.5 6.1 7.0": ["cathinones"], "-7.6 1.1 0.6": ["afterload"], "13.7 -8.1 14.2": ["acution"], "7.4 7.2 17.5": ["colores"], "2.5 11.2 7.3": ["borthers"], "11.9 -0.3 -1.2": ["harrypotter"], "-5.9 10.5 5.5": ["probationable"], "1.8 21.9 7.8": ["postdeployment"], "5.7 18.3 11.5": ["hoicks"], "12.3 2.8 9.6": ["groundscrew"], "11.1 12.3 21.2": ["thewater"], "6.4 11.1 27.8": ["matchmen"], "12.0 7.6 7.4": ["pinstriper"], "13.5 -3.6 10.8": ["crystalware"], "5.7 6.4 6.7": ["termine"], "9.0 -6.1 16.3": ["onday"], "6.6 1.6 8.5": ["dda"], "5.8 -2.3 2.2": ["scripless"], "3.8 5.6 16.5": ["rhodiola"], "-3.9 -0.7 9.0": ["laglo"], "12.9 1.3 13.3": ["jouer"], "-0.9 29.9 3.9": ["whatthey"], "1.9 2.1 21.1": ["busheling"], "10.3 5.9 40.1": ["seined"], "2.6 10.8 -0.8": ["acquisitioned"], "-0.6 18.1 7.5": ["unworldliness"], "6.7 5.7 15.7": ["solamente"], "8.5 -2.2 11.6": ["clubbier"], "14.2 0.4 14.3": ["adc"], "0.6 5.6 10.0": ["chloritization"], "4.1 9.5 12.4": ["makuuchi"], "11.0 8.8 7.4": ["securit"], "16.9 8.1 43.0": ["globefish"], "11.2 16.5 3.4": ["consequencies"], "12.7 0.8 7.4": ["metadirectory"], "-5.4 6.9 3.3": ["destino"], "-5.5 1.5 5.5": ["repr"], "20.2 18.3 6.7": ["packshot"], "4.7 26.9 12.9": ["blackhawks"], "10.5 4.0 7.2": ["landen"], "11.4 13.5 19.0": ["hurracanrana"], "16.9 20.1 16.0": ["stiffarm"], "7.1 11.9 1.5": ["capsulizes"], "8.4 1.6 8.9": ["tourisms"], "9.0 20.3 -5.2": ["becaused"], "-2.4 12.0 9.8": ["nonliterary"], "11.6 7.2 19.5": ["chulha"], "4.9 1.5 11.5": ["ysgol"], "7.2 8.6 12.6": ["kray"], "-2.4 3.5 0.2": ["oneshot"], "4.5 6.4 8.0": ["gadobutrol"], "6.6 2.7 10.5": ["paye"], "13.6 9.5 4.8": ["coupelike"], "9.9 14.1 -0.8": ["refortified"], "-0.0 9.9 9.2": ["shiftworkers"], "11.3 11.6 14.7": ["batista"], "10.7 -3.3 12.2": ["duffles"], "2.6 4.9 16.9": ["talley"], "-3.7 -3.7 8.8": ["corticoid"], "17.6 -0.7 23.1": ["akind"], "2.2 10.8 7.3": ["neopagan"], "7.3 17.3 -0.2": ["appearently"], "-7.2 -0.7 9.5": ["depos"], "-2.7 8.9 6.4": ["chools"], "8.6 9.1 9.0": ["clockspring"], "6.7 4.7 4.7": ["revv"], "-1.8 7.2 13.5": ["jensen"], "-8.9 6.3 11.2": ["magulang"], "9.8 8.8 5.8": ["affirmatives"], "4.5 8.8 1.3": ["traf"], "7.9 1.8 18.6": ["folo"], "-1.8 -0.4 14.4": ["pectus"], "13.5 -3.4 11.1": ["unstretched"], "22.8 10.2 12.6": ["microbot"], "6.6 -3.2 12.7": ["ingham"], "-3.3 10.3 -2.8": ["bestowment"], "15.6 4.9 20.3": ["klong"], "18.8 16.5 22.9": ["beatle"], "3.0 4.5 3.7": ["vounteers"], "2.6 4.3 21.3": ["gwa"], "20.2 12.3 3.5": ["gamming"], "-0.1 11.5 14.6": ["masamang"], "1.2 5.9 0.1": ["vieing"], "11.2 17.9 18.9": ["loooooooong"], "2.4 -2.6 -7.3": ["ekit"], "10.2 6.3 10.9": ["pubescents"], "0.6 12.5 9.3": ["chintan"], "17.0 21.6 25.1": ["posthole"], "-2.6 27.2 0.1": ["casualites"], "-1.8 6.1 13.3": ["resentencings"], "0.9 2.6 6.2": ["polyhydramnios"], "11.0 19.4 11.7": ["tiranga"], "13.9 6.8 32.3": ["pastina"], "7.8 19.3 6.4": ["unelect"], "9.0 3.0 8.8": ["sebagai"], "6.6 6.4 5.0": ["kdelibs"], "-0.0 -9.1 -2.4": ["slected"], "4.9 9.1 13.7": ["intestinalis"], "6.1 9.9 8.3": ["nanotags"], "-0.7 -3.2 14.1": ["osteochondrosis"], "11.2 14.9 7.6": ["unrelentless"], "15.4 3.6 28.6": ["koulourakia"], "-0.5 2.9 6.3": ["tellus"], "4.8 6.3 -2.5": ["provding"], "11.9 8.0 18.6": ["pkt"], "7.5 4.8 9.2": ["reportly"], "1.8 5.1 15.2": ["vix"], "3.0 8.1 18.2": ["tumko"], "17.0 11.8 10.8": ["genuises"], "4.9 7.7 2.2": ["semifnals"], "-0.3 8.4 10.8": ["gaothan"], "-3.7 5.5 15.4": ["fourhour"], "3.2 5.4 12.1": ["griseofulvin"], "-6.7 9.8 5.8": ["psychobiological"], "9.8 6.8 -2.6": ["specificaly"], "4.7 3.1 4.5": ["tenanting"], "6.8 1.1 19.2": ["naturale"], "17.8 9.6 10.8": ["adulterates"], "1.0 27.6 3.1": ["retaliators"], "13.7 5.5 46.0": ["pargo"], "10.9 16.2 9.8": ["humph"], "14.4 16.2 7.3": ["cowboyish"], "2.2 -4.5 1.0": ["chargedwith"], "1.4 25.1 5.1": ["outskilled"], "7.5 18.8 6.3": ["beltholders"], "3.1 13.7 14.5": ["rght"], "4.5 9.0 7.6": ["maintaned"], "-6.5 12.7 4.8": ["alais"], "9.1 17.3 10.7": ["overwith"], "-12.4 3.8 3.0": ["queenmothers"], "9.5 0.7 10.6": ["foldover"], "-0.7 9.9 13.8": ["hiyo"], "1.9 -11.9 7.8": ["quin"], "5.8 2.0 17.6": ["icks"], "-1.5 -0.6 3.9": ["oxysterols"], "-0.8 9.6 4.9": ["basewide"], "18.5 7.9 16.1": ["kouros"], "13.3 5.7 6.4": ["photocasting"], "3.4 -3.1 8.7": ["sida"], "5.3 8.9 26.5": ["hommus"], "14.9 11.7 18.2": ["rumblers"], "15.0 20.1 11.0": ["frigidly"], "11.9 9.9 13.6": ["underdrawing"], "12.8 23.4 5.2": ["botulin"], "1.7 16.1 -2.2": ["gangleader"], "5.0 -7.8 13.9": ["clinique"], "15.3 10.9 13.5": ["cratons"], "4.3 5.2 5.6": ["gibfocus"], "14.5 7.9 21.6": ["schlepper"], "-3.6 4.5 6.7": ["nonformal"], "0.9 7.9 4.3": ["epipeline"], "4.5 21.5 -1.3": ["unrehabilitated"], "-1.2 9.1 15.1": ["clemens"], "5.6 26.7 10.3": ["lankan"], "7.3 0.3 14.3": ["wihch"], "1.1 12.2 8.0": ["aswe"], "4.2 13.9 -0.8": ["influnce"], "2.5 8.2 5.4": ["limts"], "-0.7 20.4 -0.5": ["reccee"], "7.5 11.6 19.9": ["celebre"], "11.6 9.0 31.9": ["varenyky"], "-1.9 8.0 19.3": ["nootkatone"], "10.2 2.7 12.2": ["vanaf"], "16.9 -4.4 21.2": ["frillies"], "8.4 5.2 31.9": ["bagnet"], "14.0 10.3 24.4": ["muley"], "18.2 4.4 5.4": ["transreflective"], "3.5 1.7 10.7": ["kone"], "6.0 2.0 7.2": ["gabriel"], "8.6 1.4 20.9": ["lunettes"], "17.1 14.0 5.2": ["douchiest"], "3.3 3.4 17.1": ["duit"], "6.9 3.9 3.3": ["oraz"], "17.4 3.5 4.4": ["tomograph"], "14.2 16.2 -2.5": ["leades"], "-0.3 7.8 9.5": ["transparente"], "4.0 12.8 3.1": ["artefacting"], "17.7 -2.7 7.8": ["woooooo"], "0.3 18.0 6.9": ["deportability"], "8.9 11.7 15.7": ["cafecito"], "10.2 5.0 21.5": ["hydroseed"], "11.8 -1.4 13.4": ["eartag"], "9.5 9.4 16.6": ["greaves"], "5.8 7.3 9.3": ["offfer"], "14.6 15.1 23.7": ["tillandsia"], "15.7 3.3 14.0": ["uncrate"], "10.0 4.8 10.6": ["farmbelt"], "12.1 4.4 12.6": ["suply"], "4.5 0.1 6.1": ["scherzos"], "17.3 12.3 25.7": ["tickseed"], "6.1 3.4 6.1": ["shellacs"], "21.5 5.3 17.4": ["turtlenecked"], "0.4 -0.1 -3.5": ["necessiated"], "8.0 10.0 11.1": ["subsitution"], "-0.9 2.6 6.9": ["becaplermin"], "9.6 -2.9 8.1": ["relines"], "7.8 16.7 12.6": ["metalloproteins"], "6.4 16.5 11.4": ["effors"], "2.1 10.8 14.7": ["abord"], "12.6 10.3 15.1": ["doublesex"], "8.4 -2.2 -1.3": ["odontology"], "4.8 11.8 10.2": ["misssed"], "-10.1 6.3 9.6": ["reoffender"], "-2.7 12.6 3.1": ["esteeming"], "23.9 9.0 11.9": ["tomahawking"], "11.5 16.0 30.6": ["blesbok"], "-1.2 6.1 12.7": ["imbestigasyon"], "-4.3 3.9 1.2": ["interven"], "26.3 21.9 19.0": ["garuda"], "15.1 11.3 -0.4": ["wason"], "-0.1 -2.9 4.2": ["keertan"], "3.0 7.8 4.1": ["illegalized"], "5.6 3.0 4.7": ["emloyees"], "11.6 6.3 14.6": ["smegma"], "9.6 15.5 3.2": ["indissolubly"], "13.7 7.7 12.9": ["rotundity"], "8.1 13.3 0.5": ["historico"], "3.2 1.7 16.5": ["dred"], "15.7 22.3 3.5": ["technogeek"], "8.8 22.5 10.0": ["burgles"], "6.9 15.6 8.0": ["causin"], "13.8 21.3 12.3": ["ecconomy"], "7.9 19.4 8.9": ["reallllly"], "21.2 15.1 21.2": ["nickers"], "11.4 21.0 7.3": ["pepperball"], "3.5 10.8 6.3": ["alltel"], "18.2 13.8 8.2": ["claxon"], "9.6 4.1 26.0": ["kayu"], "10.6 7.0 38.4": ["dayboat"], "2.3 8.7 11.9": ["royality"], "2.4 9.2 11.4": ["steadly"], "15.1 11.6 6.8": ["scratchable"], "21.3 9.6 7.3": ["squirrelled"], "1.9 1.6 4.2": ["mss"], "4.0 8.7 4.2": ["aabout"], "17.5 12.8 25.1": ["cayuco"], "6.6 3.5 5.1": ["passses"], "-3.9 0.4 8.5": ["preponement"], "11.0 7.4 7.1": ["bingles"], "9.8 14.5 4.7": ["pwd"], "14.9 6.3 9.5": ["reshelving"], "14.7 8.1 15.9": ["pizzicati"], "5.4 3.9 18.2": ["dieu"], "17.7 6.2 23.6": ["chromes"], "13.9 12.1 33.1": ["wiliwili"], "16.2 19.0 7.7": ["facination"], "-6.9 2.6 2.0": ["duaghter"], "20.5 15.7 18.1": ["lightswitch"], "21.9 22.3 15.4": ["ensnarement"], "7.1 15.5 3.9": ["goakeeper"], "18.4 15.6 18.1": ["dutchman"], "5.4 6.7 2.0": ["disfavouring"], "-0.7 3.9 12.2": ["halalan"], "9.5 -1.0 -3.2": ["monobrand"], "15.9 7.8 14.5": ["mullen"], "8.1 -2.3 8.6": ["enw"], "1.9 4.7 -0.6": ["milligauss"], "13.8 29.2 17.1": ["ploughshare"], "-3.1 -0.9 12.1": ["preperformance"], "10.1 -0.8 11.5": ["hwang"], "3.2 16.5 3.7": ["backover"], "17.4 10.7 37.1": ["fritatta"], "19.5 17.0 11.1": ["catastophic"], "22.9 25.9 6.9": ["blackholes"], "18.8 26.2 9.5": ["apocolypse"], "4.3 10.3 16.9": ["miro"], "7.9 12.2 3.7": ["braodcast"], "1.9 2.4 -6.5": ["develping"], "9.4 11.2 18.4": ["fellside"], "14.8 8.8 6.5": ["recentralization"], "5.9 1.9 -0.3": ["judiciaire"], "11.9 17.9 3.7": ["hypocritic"], "2.8 7.7 12.8": ["canalway"], "10.7 -8.7 7.1": ["malthouse"], "14.8 4.9 12.4": ["flatish"], "5.4 -0.4 6.2": ["titude"], "36.2 -6.6 11.0": ["multimilliondollar"], "6.8 3.5 11.2": ["informaion"], "9.8 2.0 10.6": ["hellava"], "11.9 8.0 -2.3": ["whitecollar"], "-5.2 10.9 4.1": ["pandey"], "2.8 11.3 7.2": ["zafirlukast"], "11.5 9.0 24.7": ["oxpeckers"], "3.4 1.3 -9.1": ["spokeswman"], "16.0 16.3 26.6": ["knive"], "11.6 9.4 18.5": ["jete"], "7.1 6.8 6.9": ["revvy"], "12.5 4.6 40.5": ["couta"], "10.5 14.3 17.5": ["mishegas"], "1.9 20.3 14.7": ["compulsivity"], "3.6 3.5 4.7": ["zfs"], "3.7 4.0 20.9": ["rosado"], "12.4 19.2 12.6": ["ballyhoos"], "8.9 8.7 25.7": ["manhattans"], "10.8 8.5 7.6": ["medicalise"], "3.2 6.6 12.4": ["prayerbooks"], "4.7 11.6 4.7": ["btween"], "2.7 -1.4 0.7": ["chl"], "11.4 10.0 12.7": ["mornign"], "0.4 2.8 18.5": ["crianza"], "8.3 15.8 24.9": ["pocho"], "-2.3 8.2 -0.5": ["promotability"], "9.9 9.4 21.9": ["sasanquas"], "14.9 5.8 32.1": ["butterbean"], "16.3 17.2 15.9": ["paddyfields"], "10.4 9.9 25.0": ["delicioso"], "7.4 1.1 15.7": ["guajira"], "3.5 15.2 3.7": ["fulfull"], "3.6 17.8 10.3": ["prosodic"], "2.0 8.9 13.9": ["calpastatin"], "18.0 9.8 23.5": ["dabbers"], "12.3 7.7 8.9": ["plower"], "7.1 7.6 -4.4": ["transcreation"], "13.5 32.3 14.6": ["killzone"], "11.5 20.5 18.5": ["beeyotch"], "3.9 16.7 16.8": ["fumbleitis"], "-1.7 8.3 12.3": ["sakte"], "7.9 10.0 37.2": ["charmoula"], "31.3 22.7 20.6": ["triffid"], "2.8 0.5 11.8": ["nutrional"], "5.6 12.7 29.0": ["fishkeepers"], "-6.5 13.3 9.1": ["radiochemotherapy"], "4.5 5.1 1.8": ["sson"], "19.1 1.2 10.0": ["upcharges"], "9.1 -4.4 6.0": ["platesetting"], "2.9 11.5 13.2": ["sostenuto"], "-1.0 2.6 5.0": ["forestier"], "15.0 2.4 14.2": ["handstitched"], "12.4 20.3 14.4": ["tumbrels"], "9.1 13.3 10.5": ["canonising"], "4.3 -0.2 29.6": ["santan"], "-3.1 5.1 3.1": ["splanchnic"], "-1.0 18.9 11.6": ["avodah"], "6.0 16.5 6.0": ["wheelclamping"], "6.7 5.8 10.3": ["igen"], "14.3 -1.1 25.4": ["whalebones"], "-1.2 -15.6 9.1": ["urd"], "-11.4 6.3 3.4": ["poskim"], "-7.7 4.6 3.2": ["antemortem"], "15.3 15.7 6.9": ["eolian"], "14.2 6.9 6.6": ["containg"], "9.8 9.3 13.3": ["bodgie"], "-2.6 7.0 2.9": ["thoracentesis"], "15.0 8.8 11.9": ["oilworkers"], "-4.6 11.0 -4.0": ["evangel"], "16.5 4.9 20.9": ["barnwood"], "2.3 7.6 11.4": ["mattis"], "13.5 13.4 28.5": ["pebbling"], "7.6 11.1 11.3": ["dopier"], "3.8 9.9 8.6": ["yukfest"], "5.6 13.8 17.3": ["capitaine"], "6.9 14.0 -3.8": ["shudderingly"], "14.2 8.7 10.9": ["nyr"], "-0.4 6.4 8.5": ["ganjira"], "11.8 -4.2 19.3": ["yardsale"], "1.0 14.0 7.6": ["hetro"], "17.3 1.8 7.7": ["popluar"], "18.2 7.4 15.4": ["reclosure"], "11.8 1.6 7.4": ["bioartificial"], "1.0 17.3 0.6": ["illustratively"], "7.1 -7.5 5.8": ["repackagings"], "-4.3 18.0 6.4": ["desicions"], "13.1 20.8 13.1": ["gyrocopters"], "12.6 15.3 9.9": ["geosphere"], "6.8 8.2 13.3": ["overtapped"], "-2.8 10.3 12.4": ["amebiasis"], "1.6 2.3 15.9": ["scantrons"], "3.2 9.0 9.8": ["aregoing"], "-1.4 -7.8 -1.6": ["listof"], "10.9 29.8 6.8": ["netcentric"], "-1.8 0.6 8.9": ["wybodaeth"], "-3.7 10.1 -2.6": ["provisory"], "11.2 10.8 10.6": ["megaflops"], "13.7 20.2 13.8": ["vanishings"], "6.0 10.1 8.2": ["tempor"], "2.1 5.1 12.7": ["roadman"], "0.7 10.1 12.7": ["weizen"], "6.1 4.2 7.9": ["ordinaire"], "16.9 12.6 0.1": ["misdealing"], "10.9 7.8 12.5": ["nanodroplets"], "21.9 15.3 14.5": ["fandangled"], "7.0 4.8 9.6": ["angulated"], "3.1 17.2 15.5": ["desecting"], "15.4 2.1 8.6": ["greystone"], "11.3 -5.2 -0.6": ["arelooking"], "4.3 0.1 5.1": ["librarys"], "10.4 0.1 2.5": ["rennovated"], "14.0 12.1 30.0": ["winnie"], "0.1 10.1 10.2": ["fitra"], "7.5 15.0 0.9": ["particluar"], "3.9 15.8 -4.4": ["deplanes"], "1.9 3.9 7.3": ["bano"], "8.8 4.0 26.7": ["sesamum"], "1.7 9.6 8.3": ["amader"], "1.9 11.1 11.2": ["strikelength"], "-9.0 8.6 9.4": ["undersheriffs"], "7.4 16.8 4.8": ["arshavin"], "15.3 14.3 11.6": ["tinmankind"], "-1.6 6.3 -1.7": ["perview"], "0.3 9.5 -1.3": ["descoping"], "5.5 11.3 -0.5": ["unparalelled"], "8.5 7.4 19.6": ["waitrons"], "0.8 3.6 8.6": ["metalling"], "12.2 -2.0 7.0": ["wetcleaning"], "5.6 2.4 7.1": ["pycnogenol"], "6.6 -7.4 2.9": ["fourbedroom"], "22.4 21.0 17.7": ["pommie"], "-1.5 5.2 15.4": ["acidities"], "7.0 6.8 18.9": ["wkend"], "3.5 14.8 11.3": ["occiput"], "22.5 17.1 35.3": ["lungless"], "8.6 13.2 12.6": ["diatremes"], "9.4 10.3 8.4": ["searchandising"], "6.2 5.5 1.5": ["propone"], "1.4 6.5 8.4": ["tinzaparin"], "10.5 18.8 9.4": ["guvment"], "10.4 9.1 0.6": ["mygofer"], "6.2 -0.1 9.9": ["ethoxylate"], "16.6 5.4 17.3": ["hatmakers"], "14.3 14.8 21.2": ["drogues"], "12.8 16.0 14.0": ["hyperfocused"], "-2.3 11.9 14.5": ["ineligibles"], "-8.0 7.9 4.6": ["committable"], "-5.9 9.9 0.7": ["fify"], "4.5 5.7 24.4": ["carpus"], "1.6 2.2 4.2": ["periprosthetic"], "16.2 11.1 10.1": ["cutesie"], "1.6 5.6 15.2": ["underdress"], "10.1 17.4 12.8": ["zem"], "8.5 5.1 8.5": ["yaun"], "2.3 6.7 8.3": ["nitrided"], "3.2 2.1 8.4": ["nonagriculture"], "22.7 -2.4 1.8": ["busmaker"], "2.9 24.2 14.9": ["outstrike"], "18.0 -2.1 1.6": ["npd"], "12.8 11.1 11.5": ["superpredators"], "5.1 -6.6 12.9": ["microminis"], "10.8 15.0 31.8": ["gyrfalcons"], "7.8 25.1 10.8": ["eradicable"], "2.0 9.1 18.5": ["costwise"], "6.6 -1.8 8.1": ["piperacillin"], "-1.5 12.9 3.2": ["fustrated"], "15.1 11.3 17.3": ["torenia"], "18.3 13.5 15.3": ["opiated"], "7.8 22.9 8.8": ["conviently"], "2.7 4.4 3.2": ["dragflick"], "6.5 10.2 4.9": ["meagrely"], "-4.8 6.1 5.3": ["ongong"], "7.7 9.1 20.6": ["skite"], "11.9 8.7 4.9": ["casseurs"], "4.0 16.8 5.1": ["ministerially"], "4.9 11.0 6.8": ["ifconfig"], "6.2 12.4 7.0": ["cattiest"], "10.1 23.7 15.6": ["swarmer"], "2.4 34.0 10.3": ["dogfaces"], "16.6 13.1 13.7": ["itsself"], "7.8 -0.2 16.5": ["eleni"], "4.9 -4.6 16.0": ["octavo"], "0.1 -0.8 15.1": ["oneweek"], "12.4 15.1 23.6": ["busta"], "14.0 0.7 21.3": ["jalape"], "-5.9 5.4 -1.1": ["versified"], "1.8 7.0 -5.0": ["unconcluded"], "13.4 16.8 14.0": ["embarassments"], "11.3 13.5 10.7": ["consious"], "8.2 10.1 13.9": ["wordsmithery"], "-0.0 21.9 1.8": ["uncaused"], "10.6 18.1 42.5": ["postspawn"], "5.5 8.6 6.8": ["sensi"], "4.5 3.9 9.9": ["dayz"], "10.5 25.3 16.6": ["koreans"], "4.5 -3.4 3.3": ["experiencia"], "4.1 5.1 3.5": ["verma"], "5.4 0.1 9.9": ["operatingincome"], "10.5 2.0 13.0": ["sella"], "11.0 16.3 10.3": ["caricaturish"], "14.2 -0.1 13.2": ["polyphosphates"], "7.6 6.2 8.8": ["microdomains"], "3.5 -6.0 8.6": ["gestion"], "-1.6 11.4 8.9": ["pranksterism"], "0.1 15.8 15.4": ["junoon"], "12.6 3.5 8.1": ["stook"], "15.3 5.1 14.3": ["turvy"], "-0.9 7.5 6.6": ["mandali"], "-1.8 9.4 7.1": ["sokoto"], "6.3 10.3 6.3": ["forsight"], "-0.3 -5.2 -0.4": ["educationals"], "17.8 18.7 28.5": ["teethmarks"], "-0.2 9.4 6.1": ["verba"], "4.7 13.8 6.8": ["fireraising"], "6.5 -8.4 7.1": ["staffmember"], "18.2 5.5 26.5": ["piroshki"], "3.5 11.8 13.6": ["brickfield"], "5.0 9.0 16.1": ["padrinos"], "-1.2 10.1 8.0": ["panyards"], "4.8 12.6 12.3": ["awlful"], "-3.4 11.4 2.8": ["potentiator"], "-1.1 16.6 7.0": ["antedate"], "15.0 6.9 9.5": ["profitablility"], "-2.2 25.5 17.4": ["impressment"], "1.9 1.5 2.6": ["burnup"], "0.5 10.8 14.9": ["pleiotrophin"], "10.7 6.1 14.6": ["cpanel"], "11.1 9.8 13.0": ["runnels"], "11.4 14.7 14.7": ["turrible"], "2.9 10.0 4.4": ["intermixes"], "1.1 7.1 11.1": ["tautoko"], "7.4 3.8 24.3": ["sativum"], "8.0 -6.9 13.2": ["punds"], "20.4 12.9 22.3": ["moistly"], "14.2 3.9 4.2": ["payzone"], "17.0 15.0 20.3": ["shepards"], "-2.8 11.6 5.5": ["hypercoagulability"], "7.1 22.7 9.3": ["blackhearted"], "3.9 34.6 7.1": ["katyushas"], "8.4 6.7 31.4": ["chimaeras"], "1.2 20.4 -1.3": ["collocutors"], "12.6 13.8 9.1": ["liberalness"], "13.7 7.9 6.5": ["miswired"], "11.0 12.8 13.5": ["bule"], "5.5 12.7 7.7": ["ohter"], "14.1 11.6 12.6": ["friskiest"], "7.8 9.3 13.7": ["ahvincent"], "11.5 13.5 -7.9": ["frogmarch"], "10.7 20.6 12.6": ["unsymmetrical"], "15.4 14.6 11.9": ["faling"], "0.0 11.4 13.2": ["divertimento"], "14.8 9.6 -2.2": ["videoblogger"], "13.7 14.3 7.8": ["tintinnabulation"], "11.1 -0.9 1.0": ["subpoenaes"], "5.5 11.4 14.8": ["neque"], "5.5 12.0 13.1": ["yelpers"], "-1.1 0.2 11.6": ["tohold"], "4.6 4.1 8.8": ["toxicogenomic"], "14.4 9.0 -1.5": ["gusle"], "0.8 4.0 16.3": ["crotchets"], "6.8 -1.2 -3.8": ["themanagement"], "3.7 12.3 6.0": ["assing"], "0.8 0.3 5.5": ["tradeability"], "2.1 2.0 9.8": ["benicar"], "7.9 7.0 5.1": ["enculturated"], "6.2 11.1 19.1": ["cocci"], "6.2 11.5 4.0": ["bosonic"], "19.3 9.5 9.4": ["coffeetable"], "15.3 10.1 16.0": ["americanum"], "14.4 13.3 34.7": ["drupes"], "20.4 9.2 15.4": ["hennaed"], "7.4 9.8 14.8": ["beerhall"], "3.0 3.6 9.1": ["signicantly"], "18.2 15.9 14.1": ["menials"], "5.2 3.9 17.3": ["sudsers"], "6.0 1.4 9.4": ["esas"], "15.4 7.9 23.6": ["loofa"], "7.5 19.2 1.7": ["supicious"], "14.5 -1.2 4.9": ["micrographics"], "3.3 0.9 2.9": ["ppr"], "2.4 13.1 2.3": ["picometer"], "-1.0 7.1 2.8": ["aruged"], "19.5 13.2 24.0": ["whomps"], "4.4 5.8 -1.4": ["multihoming"], "1.6 3.3 11.2": ["continuingoperations"], "0.8 28.0 4.3": ["mullocracy"], "10.1 13.3 17.7": ["winterscape"], "-0.5 -1.4 11.0": ["vilambit"], "-1.9 5.3 8.6": ["hypoactive"], "8.6 -6.1 -0.1": ["voda"], "8.2 13.5 13.5": ["biotopes"], "6.6 3.7 21.0": ["ensiled"], "15.2 5.1 6.1": ["trimmest"], "5.2 3.1 5.7": ["somwhat"], "10.3 3.3 19.4": ["inkpad"], "-5.6 -0.5 1.7": ["investig"], "9.6 5.4 13.6": ["seatstay"], "1.6 -1.1 1.1": ["commerciales"], "8.5 -8.1 1.9": ["pagaent"], "8.7 6.2 3.8": ["attrack"], "10.8 10.6 10.1": ["ssundaztood"], "9.5 21.9 18.6": ["gameface"], "5.5 21.3 18.4": ["sunburning"], "-2.0 19.9 4.1": ["policital"], "14.0 17.3 10.3": ["countercoups"], "4.7 10.7 -1.7": ["conected"], "19.4 11.6 0.3": ["skyrockit"], "2.3 4.8 8.1": ["logue"], "8.9 7.4 15.2": ["bikeshare"], "11.4 16.7 3.7": ["litigiously"], "3.2 13.6 11.8": ["bhaiyyas"], "20.5 2.2 37.9": ["poulty"], "0.3 7.0 12.5": ["mastoiditis"], "-5.5 11.5 -1.3": ["antifibrinolytic"], "2.7 18.6 5.6": ["ascetical"], "19.9 8.8 15.9": ["foldouts"], "18.5 10.9 13.7": ["wouldja"], "13.6 8.6 13.7": ["silverwear"], "-0.3 3.3 13.6": ["nontreated"], "1.8 8.9 14.3": ["drippingly"], "3.7 14.4 11.9": ["euchromatin"], "-11.8 19.6 -1.6": ["chioce"], "13.4 12.9 12.5": ["globalchange"], "8.0 5.7 7.8": ["conacre"], "-2.6 25.4 10.7": ["situationists"], "3.5 1.7 2.3": ["aci"], "2.8 -2.5 16.7": ["sparklings"], "2.5 14.8 1.7": ["potrayal"], "16.5 5.4 25.8": ["pannini"], "5.9 19.6 9.5": ["flamingly"], "3.5 16.3 4.8": ["clerically"], "5.7 17.6 5.2": ["techincally"], "3.9 32.2 8.0": ["abominate"], "-3.3 11.2 16.8": ["bumalik"], "8.0 6.8 10.2": ["tarded"], "-10.7 3.1 6.3": ["nonemergent"], "1.4 7.0 -1.8": ["showd"], "12.4 14.3 14.4": ["glyphosphate"], "10.9 2.5 27.6": ["phad"], "12.4 -2.6 9.8": ["bega"], "6.1 5.8 0.1": ["iisu"], "13.6 -0.6 5.8": ["crossholding"], "24.8 7.5 23.6": ["roesti"], "15.4 -0.3 15.2": ["fh"], "12.3 15.9 13.4": ["cougs"], "-0.7 2.0 1.0": ["usac"], "-1.7 1.8 3.9": ["decribing"], "13.5 5.0 20.6": ["patinaed"], "11.4 16.6 9.7": ["guantlet"], "5.4 14.1 9.1": ["savegame"], "19.7 8.5 11.4": ["electonics"], "9.3 -2.6 7.3": ["beneft"], "10.3 13.6 14.3": ["reeeally"], "6.4 6.0 10.1": ["ccy"], "1.3 19.9 7.4": ["perspicuity"], "13.1 3.3 22.2": ["crambe"], "22.6 12.0 14.6": ["slanty"], "7.2 4.9 -0.1": ["seamonkey"], "9.0 -1.6 31.0": ["muffalettas"], "-11.0 3.3 3.7": ["constitutencies"], "7.5 6.8 8.9": ["shriners"], "18.0 14.0 10.1": ["dopily"], "-2.8 12.4 3.2": ["assiting"], "-10.0 -3.7 15.1": ["lio"], "12.7 12.0 12.4": ["michaeltan"], "9.9 18.9 6.5": ["peeving"], "1.5 6.5 19.7": ["smo"], "11.5 17.8 19.1": ["pumphandle"], "0.7 9.9 13.5": ["purus"], "21.8 14.6 10.5": ["astroturfed"], "7.6 9.1 24.8": ["poule"], "3.6 -5.5 8.1": ["ulated"], "0.6 8.5 11.2": ["tumhari"], "9.6 -0.4 10.0": ["nomic"], "-6.0 4.2 23.4": ["resorters"], "-3.6 19.9 8.5": ["goig"], "9.2 18.9 15.9": ["ballists"], "7.0 0.4 -2.0": ["servie"], "15.2 3.7 8.1": ["brickmakers"], "16.3 9.5 8.7": ["electrohouse"], "-6.8 5.0 6.6": ["heparanase"], "23.5 20.2 4.5": ["itelf"], "9.4 -2.2 16.9": ["stanol"], "12.2 14.8 26.2": ["dusks"], "3.9 19.8 16.2": ["locke"], "0.1 -0.7 11.5": ["hypocalcaemia"], "17.1 5.3 24.4": ["labradorite"], "1.5 14.2 7.4": ["vade"], "10.7 1.4 11.0": ["ultrafeminine"], "16.8 18.0 16.0": ["chubbies"], "11.0 8.4 36.6": ["handlining"], "-9.6 3.4 5.2": ["kaduna"], "1.2 19.2 -1.2": ["provokingly"], "8.1 1.4 13.5": ["dodd"], "13.3 5.6 15.5": ["trilion"], "-7.8 5.7 1.4": ["ofpatients"], "2.5 6.7 15.9": ["maang"], "17.4 14.5 25.3": ["upswelling"], "4.4 9.8 5.4": ["teenages"], "7.8 5.9 15.9": ["ppvs"], "5.3 15.1 17.6": ["munted"], "14.6 8.3 18.0": ["silnylon"], "8.2 17.8 15.9": ["ripsnorter"], "-0.8 5.3 9.8": ["adenomatous"], "6.8 17.4 8.6": ["inablity"], "13.4 3.9 10.8": ["systen"], "17.7 19.6 13.5": ["punchable"], "9.0 -0.9 13.9": ["roulez"], "1.7 9.9 17.6": ["styes"], "-2.5 1.5 12.4": ["hapon"], "19.9 17.7 19.5": ["wineskin"], "4.9 2.7 9.4": ["shortlines"], "1.0 -10.7 -2.1": ["expectes"], "22.3 -2.9 7.7": ["bequiffed"], "21.7 16.4 26.9": ["napes"], "14.2 20.2 5.9": ["antitrade"], "16.7 -1.1 3.0": ["rebrandings"], "5.4 9.2 18.8": ["halwai"], "9.2 11.8 11.1": ["spectrograms"], "19.5 13.9 21.8": ["raffishly"], "-5.1 10.8 14.7": ["menstruates"], "0.3 7.5 10.6": ["rewinded"], "-8.9 4.0 6.2": ["uation"], "2.8 12.2 5.3": ["systemise"], "8.3 8.6 5.8": ["glamourize"], "5.3 19.6 16.1": ["luckiness"], "9.6 19.5 -1.1": ["protaganists"], "24.3 18.0 26.8": ["frogger"], "21.5 16.9 26.6": ["sticklike"], "7.5 8.2 22.4": ["cineraria"], "12.1 1.0 16.7": ["nestegg"], "3.1 -0.4 -9.0": ["joines"], "-3.1 4.4 -0.0": ["druidry"], "8.0 8.0 8.2": ["patri"], "7.6 12.7 8.2": ["prostidude"], "11.1 11.9 24.5": ["kanuka"], "-5.0 9.2 5.2": ["schpiel"], "7.9 -7.5 -3.0": ["whichincludes"], "1.9 12.1 18.3": ["historicalfacts"], "7.9 18.1 14.2": ["haff"], "10.8 4.5 3.0": ["foresights"], "-7.2 6.1 4.5": ["gastroduodenal"], "9.4 7.2 11.9": ["hydronics"], "23.6 12.5 3.2": ["superjet"], "11.3 10.8 7.3": ["undampened"], "11.2 9.4 17.4": ["unbaptised"], "17.8 4.2 17.9": ["zipwire"], "9.1 4.7 6.7": ["toolsuite"], "7.4 13.0 13.8": ["economicgrowth"], "-4.0 -1.1 3.0": ["nonhealth"], "3.5 6.2 2.6": ["reciving"], "13.9 11.3 23.3": ["ringworms"], "5.6 12.5 10.3": ["boulderers"], "5.0 12.7 8.6": ["halocarbons"], "10.9 16.0 11.1": ["ahistoric"], "-1.3 3.3 11.3": ["ergogenic"], "12.1 5.5 24.3": ["cedary"], "0.1 2.0 25.9": ["grapefruity"], "-2.9 18.7 4.1": ["sacrafices"], "13.8 5.9 22.6": ["woodfire"], "9.2 9.5 32.1": ["seekh"], "2.8 8.7 10.4": ["midband"], "-1.0 1.3 9.2": ["eosin"], "1.7 9.1 26.0": ["scarceness"], "7.4 15.0 14.9": ["uve"], "7.0 11.7 13.5": ["sexbots"], "1.3 7.1 4.8": ["thinkteam"], "0.3 -1.4 0.4": ["indometacin"], "-1.4 12.4 9.1": ["youngesters"], "7.1 12.4 19.8": ["florally"], "6.3 12.5 1.9": ["leglislation"], "4.2 7.3 -3.5": ["arenow"], "11.5 5.8 11.7": ["densitometers"], "7.6 -10.1 0.5": ["wned"], "-4.4 -3.3 -12.0": ["connectionwith"], "-1.6 2.0 8.5": ["aliqua"], "11.9 3.1 14.0": ["xpdf"], "14.5 14.3 15.5": ["unspecial"], "8.4 8.4 15.0": ["luvin"], "11.8 13.8 14.2": ["seemes"], "0.9 10.7 5.2": ["defecits"], "6.8 7.9 10.3": ["rageous"], "6.4 16.7 8.7": ["decarbonized"], "18.5 -4.0 -1.0": ["lnc"], "10.6 4.3 10.4": ["econonic"], "7.7 0.3 16.1": ["galloon"], "15.3 28.8 19.2": ["blunderbusses"], "9.4 6.0 17.0": ["quillwork"], "7.6 16.7 5.7": ["posiiton"], "6.8 10.8 10.2": ["submucosa"], "23.0 3.9 31.2": ["chipolata"], "4.4 -0.3 9.1": ["triennially"], "2.4 5.5 9.4": ["andeconomic"], "-2.9 23.2 2.5": ["acknowleded"], "4.2 0.0 7.3": ["chattily"], "-0.9 4.2 7.1": ["rusticate"], "1.0 5.7 9.9": ["propoor"], "12.5 12.5 12.3": ["sparging"], "5.0 5.4 13.0": ["gey"], "3.4 8.9 13.2": ["headcoverings"], "21.5 14.8 10.6": ["quangocracy"], "-0.0 13.3 14.3": ["bastardizations"], "8.1 0.1 -9.6": ["analys"], "9.3 5.0 21.3": ["pooram"], "23.2 4.3 2.7": ["datacoms"], "6.9 18.9 10.0": ["dewetting"], "0.9 10.1 4.1": ["anding"], "15.4 7.6 1.8": ["explotation"], "0.3 9.2 14.3": ["adventerous"], "5.0 0.2 8.1": ["orthoimagery"], "2.7 13.5 11.5": ["rhythmicity"], "10.0 -2.6 9.5": ["flts"], "15.7 -1.7 10.7": ["perfluorinated"], "13.3 -1.8 3.3": ["miljoen"], "2.8 5.0 7.0": ["shaam"], "12.9 5.8 -6.2": ["ereading"], "-4.4 4.0 -0.5": ["ciation"], "5.9 5.4 22.6": ["mastman"], "9.3 -2.6 3.1": ["timefor"], "1.4 14.1 3.7": ["convivencia"], "0.1 7.0 11.4": ["chlordecone"], "13.2 14.6 19.3": ["leopardess"], "0.6 3.4 6.0": ["ignimbrites"], "14.7 16.5 8.7": ["slapfight"], "17.3 11.7 31.4": ["rockpools"], "5.6 12.5 8.3": ["filingswith"], "19.4 -6.0 7.2": ["agroprocessing"], "-10.8 2.9 -8.5": ["assistent"], "0.1 -6.9 2.3": ["libvirt"], "13.0 2.0 12.6": ["camry"], "-2.8 8.2 10.8": ["remem"], "-0.9 -1.8 6.1": ["clubbites"], "-2.3 -6.8 4.2": ["ingage"], "5.8 8.6 11.9": ["thia"], "8.1 4.0 35.6": ["netsmen"], "5.9 19.3 4.7": ["disinteresting"], "14.5 8.9 32.7": ["wheatear"], "8.7 -6.6 13.4": ["kanssa"], "9.5 13.7 7.0": ["abbe"], "8.7 19.8 4.0": ["isomorphic"], "-0.3 2.0 9.3": ["careerbest"], "12.4 6.2 21.6": ["opalescence"], "-0.5 6.0 11.5": ["polyimides"], "6.6 0.6 8.5": ["aproximadamente"], "11.9 6.3 11.8": ["housecleanings"], "-0.9 18.7 11.0": ["chhod"], "-3.4 9.2 8.1": ["cystoscopic"], "26.4 6.9 16.4": ["zorb"], "9.9 11.8 4.4": ["capabale"], "2.3 9.4 10.0": ["thermowells"], "-1.3 -0.3 2.9": ["minicard"], "14.3 3.4 13.1": ["preloved"], "5.4 13.6 13.0": ["favortie"], "7.6 9.9 12.6": ["tempestuousness"], "-0.9 7.9 11.5": ["selectpersons"], "-3.4 7.2 14.4": ["ibu"], "3.9 21.1 11.2": ["najis"], "5.3 21.6 14.4": ["populaton"], "7.2 8.7 19.8": ["kapparot"], "5.1 11.3 6.9": ["recategorize"], "9.2 12.0 33.0": ["juk"], "7.8 5.4 16.9": ["interplaying"], "-0.9 5.0 8.1": ["ferrofluids"], "7.2 9.2 8.4": ["naacp"], "9.6 -5.9 1.4": ["hci"], "5.0 5.9 -0.9": ["agee"], "5.7 9.0 1.5": ["indefinate"], "0.8 9.5 10.1": ["tachypnea"], "7.2 12.2 37.7": ["kelah"], "8.0 16.5 12.4": ["rogered"], "10.4 19.2 13.8": ["hereditarily"], "3.3 4.7 9.3": ["sparticles"], "-7.6 10.7 3.7": ["conformality"], "10.5 16.3 5.8": ["blocade"], "8.6 19.5 10.1": ["chowderhead"], "-6.1 7.7 8.5": ["oir"], "15.6 7.1 10.2": ["heirhead"], "5.5 4.4 8.5": ["roko"], "3.4 10.2 17.8": ["coldwave"], "15.5 26.0 13.8": ["whoomph"], "0.3 3.6 8.4": ["microalbumin"], "14.2 9.9 13.5": ["virtualbox"], "2.2 13.6 7.8": ["dimentia"], "-1.7 8.7 8.0": ["dham"], "15.9 4.8 27.7": ["carobs"], "5.7 4.1 1.5": ["anamnesis"], "9.3 15.5 -0.2": ["obtrusiveness"], "6.2 10.4 18.0": ["polypoid"], "3.2 2.8 9.1": ["aston"], "4.9 9.1 -4.0": ["shouls"], "0.7 19.8 5.9": ["peaple"], "2.0 2.1 2.8": ["polyethylenes"], "8.7 15.6 34.8": ["muddlers"], "13.1 6.0 4.0": ["nanofilm"], "12.7 0.5 2.0": ["agt"], "2.5 9.9 3.8": ["gurbani"], "11.2 6.6 7.8": ["zonder"], "13.6 3.0 -2.8": ["typcially"], "25.6 6.7 17.1": ["skyrocketting"], "3.4 3.5 1.6": ["accomidate"], "-0.6 14.8 4.1": ["electibility"], "7.8 15.7 6.3": ["altnets"], "17.6 7.0 10.1": ["threader"], "15.7 1.6 12.5": ["cruelling"], "9.5 15.6 24.7": ["motus"], "10.3 6.1 11.6": ["stereoscopes"], "6.9 9.4 18.3": ["orientale"], "0.8 -1.3 8.1": ["progestogens"], "21.9 8.1 9.9": ["spacewoman"], "10.0 16.0 8.8": ["reminescent"], "15.5 17.0 43.1": ["dropshotting"], "-0.7 14.2 6.0": ["cemevi"], "19.9 11.7 23.3": ["hawkmoth"], "20.3 6.8 23.8": ["pouchy"], "-2.7 12.0 4.3": ["imran"], "4.0 7.6 15.7": ["nonwealthy"], "13.2 1.7 30.5": ["tiao"], "12.4 2.2 1.5": ["fetchtv"], "5.1 23.1 16.2": ["subo"], "4.7 2.1 14.5": ["shantos"], "5.0 15.3 17.7": ["crumber"], "-4.5 3.3 -3.2": ["hasmade"], "-5.4 6.0 -2.7": ["commande"], "11.3 1.3 9.8": ["intermittingly"], "3.0 11.4 3.7": ["possesssion"], "6.4 5.6 6.2": ["veru"], "8.3 -0.2 17.0": ["snowskate"], "6.6 19.6 8.5": ["surivors"], "0.8 8.1 4.1": ["proceso"], "-2.4 1.4 2.2": ["kavi"], "16.4 24.5 -2.6": ["multiconfessional"], "18.2 2.2 13.9": ["moppy"], "2.7 0.5 12.2": ["mscf"], "11.1 6.2 6.6": ["forseeing"], "10.6 -0.4 41.3": ["involtini"], "14.2 1.4 10.1": ["precommercial"], "23.5 3.8 6.7": ["spokescharacters"], "3.7 0.9 14.1": ["umano"], "9.4 4.8 15.9": ["paradores"], "5.4 21.7 6.5": ["vulgarisation"], "-5.6 11.3 -5.0": ["invigilated"], "-0.8 21.7 11.3": ["inconsistancy"], "5.0 25.9 13.3": ["suspence"], "5.9 -0.6 2.4": ["oved"], "10.3 10.5 4.2": ["corprate"], "5.5 6.7 5.6": ["rowen"], "7.7 16.6 10.3": ["interferograms"], "7.5 10.2 15.1": ["bordatella"], "1.0 11.1 8.1": ["amman"], "9.3 17.1 9.6": ["unhonored"], "-2.6 17.0 5.5": ["tostay"], "18.1 22.0 11.5": ["crackpottery"], "14.3 5.1 -5.7": ["webportal"], "15.3 4.8 10.7": ["luego"], "4.4 8.3 2.4": ["presss"], "7.3 19.5 12.6": ["overarches"], "2.1 18.5 6.5": ["excitotoxins"], "12.0 13.8 12.6": ["leeringly"], "2.7 8.2 8.2": ["cwg"], "0.8 -1.5 8.2": ["dano"], "5.9 5.5 10.2": ["intuitives"], "-3.8 4.0 5.1": ["provinical"], "1.3 14.1 12.2": ["eotyrannus"], "11.6 11.3 7.3": ["shiftily"], "3.5 6.5 12.9": ["previa"], "1.6 3.7 6.7": ["hyoscine"], "1.7 -5.2 3.9": ["biotherapies"], "18.0 2.2 11.9": ["cashboxes"], "15.2 15.9 3.3": ["tricorders"], "12.3 3.0 8.8": ["shakira"], "7.7 8.1 18.0": ["tranship"], "7.1 15.7 0.2": ["negetive"], "-4.5 11.1 6.0": ["constituences"], "10.5 19.6 14.8": ["saccade"], "9.2 3.5 10.2": ["recov"], "5.7 3.1 14.5": ["mabilis"], "8.5 27.3 12.5": ["suiciding"], "6.3 20.4 6.7": ["discrace"], "18.7 16.8 11.4": ["kishi"], "21.7 11.4 11.0": ["wordsearch"], "20.5 2.0 3.6": ["donwload"], "2.3 6.0 -1.0": ["neues"], "4.5 12.3 6.9": ["huckabee"], "9.2 -7.2 4.7": ["emb"], "-0.4 4.0 3.2": ["speechs"], "11.7 10.6 6.4": ["querulously"], "-8.4 0.0 16.5": ["enrollement"], "2.5 9.7 16.4": ["shambas"], "3.2 5.6 10.4": ["viscoelasticity"], "12.9 22.0 1.6": ["unblinkered"], "16.1 12.3 21.7": ["heapings"], "20.1 15.3 22.1": ["damply"], "15.4 16.0 35.7": ["willet"], "6.6 5.9 8.1": ["denken"], "4.1 2.7 3.5": ["fulll"], "0.4 5.6 3.5": ["qadi"], "13.4 -0.6 -1.0": ["exas"], "19.7 4.1 19.8": ["titfer"], "6.6 0.9 1.0": ["livecast"], "7.0 7.1 7.6": ["coldfusion"], "9.0 12.2 10.5": ["regripping"], "13.0 9.9 8.3": ["adorbs"], "8.8 11.9 4.4": ["birdstrikes"], "12.1 7.5 6.1": ["nonstandardized"], "6.1 8.3 10.8": ["blan"], "13.6 26.8 19.4": ["haints"], "2.5 10.0 11.4": ["progession"], "-0.9 7.0 7.1": ["baycas"], "-0.3 8.2 2.8": ["immunoblot"], "13.0 30.8 16.2": ["bombies"], "2.1 1.4 3.8": ["dummer"], "7.9 6.6 16.3": ["diffusor"], "-1.3 18.0 4.0": ["coverman"], "2.7 6.1 18.4": ["verra"], "7.7 -2.7 3.4": ["aspirators"], "3.0 3.1 5.2": ["biguanide"], "-4.5 2.2 6.9": ["sentanced"], "14.3 24.4 0.3": ["semisecret"], "10.0 12.0 12.1": ["rolemodel"], "0.2 16.2 2.6": ["releasee"], "5.6 13.6 8.2": ["optogenetic"], "3.5 21.2 9.6": ["youwant"], "15.3 11.0 21.0": ["tympanum"], "15.2 -3.0 18.7": ["rossa"], "9.4 -2.5 7.4": ["reti"], "-1.3 17.2 -1.3": ["plagiarisms"], "23.2 11.2 22.4": ["cornpads"], "13.3 9.1 11.2": ["theline"], "15.6 12.8 20.5": ["santuary"], "-0.6 3.1 -4.0": ["intercreditor"], "4.8 21.9 3.1": ["localiser"], "6.4 7.3 22.0": ["anklebone"], "-0.2 1.7 7.9": ["shox"], "0.2 -0.8 -3.2": ["sugested"], "15.4 6.7 29.5": ["pliosaurs"], "15.6 10.5 16.6": ["footmark"], "24.6 20.9 20.3": ["expressionlessly"], "7.5 10.0 12.4": ["eggheaded"], "27.8 6.7 20.1": ["censers"], "19.4 22.4 21.6": ["divebombing"], "16.2 24.7 47.2": ["linesider"], "2.5 -3.1 7.4": ["downgauging"], "-0.2 9.4 8.1": ["plusers"], "6.2 5.2 4.8": ["partout"], "8.0 16.1 7.2": ["outmarked"], "-3.0 9.9 3.2": ["micafungin"], "6.0 4.2 10.6": ["fivepoint"], "6.6 21.2 5.3": ["wirklich"], "4.2 17.4 21.9": ["mintmarks"], "7.5 27.2 7.0": ["conspiracism"], "0.2 4.2 23.9": ["dalia"], "12.0 10.5 -0.4": ["relayer"], "24.9 1.5 5.1": ["divis"], "8.3 12.7 10.1": ["tibi"], "8.1 11.9 10.5": ["inanition"], "6.7 -3.7 2.7": ["carman"], "10.9 12.8 10.7": ["studmuffin"], "2.0 13.0 1.8": ["ively"], "1.4 -4.1 5.6": ["includethe"], "9.7 3.8 3.6": ["bekommen"], "12.7 26.2 10.8": ["zombify"], "4.4 2.3 1.9": ["klar"], "19.9 13.3 20.4": ["loooooove"], "24.8 5.3 7.9": ["permatemps"], "7.0 5.1 12.1": ["xorg"], "-4.1 17.1 4.9": ["anthroposophy"], "4.6 2.0 7.1": ["cortizone"], "16.1 16.6 10.6": ["megafunds"], "8.5 1.7 0.7": ["geoinformatics"], "13.6 14.9 18.0": ["thickos"], "3.4 4.3 17.0": ["quadrathlon"], "17.3 11.5 29.1": ["forequarters"], "-3.4 4.3 9.6": ["nonblocking"], "19.8 4.8 18.4": ["crosspieces"], "2.6 18.2 2.7": ["ammuntion"], "5.2 7.9 1.3": ["quited"], "0.2 9.7 -7.1": ["majorty"], "0.3 14.6 8.4": ["chanceto"], "-1.0 7.8 14.7": ["cag"], "2.3 8.5 4.3": ["bleibt"], "-2.7 10.9 12.4": ["multilateralization"], "-0.9 6.9 9.6": ["yisrael"], "5.2 5.9 7.7": ["hypersensitivities"], "5.5 7.9 11.3": ["quadrennially"], "3.1 1.6 17.6": ["ozt"], "-2.0 4.4 8.7": ["uted"], "10.0 -7.6 8.8": ["natiowide"], "13.0 4.1 14.7": ["frits"], "8.9 8.9 18.3": ["pregs"], "-1.8 23.3 10.1": ["foce"], "16.7 7.6 12.2": ["resizer"], "-7.9 8.3 -0.4": ["academical"], "1.7 -5.0 1.5": ["nrg"], "9.7 5.0 7.6": ["uesday"], "4.0 5.8 8.9": ["revisal"], "14.6 10.9 15.3": ["smugger"], "7.9 -1.3 14.5": ["aros"], "15.3 11.5 6.8": ["attacts"], "6.9 4.6 18.2": ["bullrun"], "4.9 9.1 9.0": ["ahome"], "8.0 3.8 8.0": ["resultado"], "13.3 23.6 10.9": ["supergenius"], "-1.5 11.7 0.9": ["communicatively"], "4.0 0.1 15.0": ["columbium"], "9.5 7.9 1.0": ["romanized"], "17.0 15.2 23.0": ["porkie"], "14.8 10.8 50.4": ["linesides"], "-1.1 8.6 8.2": ["predeparture"], "-6.8 20.9 1.4": ["dicated"], "9.2 0.9 12.3": ["microlaser"], "7.6 4.0 15.5": ["dressiest"], "-3.3 -5.8 7.7": ["receipent"], "-8.5 11.2 -1.9": ["nately"], "10.1 6.7 3.3": ["xox"], "7.3 3.9 5.7": ["approche"], "2.9 2.9 1.8": ["streetworks"], "3.8 15.3 12.9": ["winston"], "3.9 8.1 13.2": ["concupiscent"], "8.6 13.4 16.9": ["dmhack"], "19.9 11.0 25.1": ["whaleback"], "5.7 6.1 10.0": ["oarswoman"], "-4.0 13.5 4.9": ["jetbridge"], "8.4 15.1 10.9": ["doenst"], "0.8 -0.1 -0.3": ["bikeability"], "3.6 10.8 7.3": ["unm"], "23.4 1.8 9.0": ["miniboom"], "6.2 24.7 25.3": ["foos"], "9.2 17.9 14.2": ["dissapearing"], "6.6 0.2 10.1": ["healthinsurance"], "14.8 17.1 10.5": ["budgeteer"], "10.8 6.7 32.9": ["escapements"], "-1.4 9.2 2.5": ["firedoglake"], "14.3 7.4 10.0": ["espies"], "9.4 7.3 22.0": ["frutescens"], "5.6 11.5 22.4": ["cryer"], "6.5 1.9 -0.5": ["postbags"], "9.2 4.7 7.6": ["ichat"], "18.0 14.6 9.2": ["tanty"], "2.1 4.7 8.7": ["nitrotyrosine"], "3.4 2.1 -4.0": ["availabile"], "7.2 1.5 9.6": ["misma"], "13.3 9.0 19.0": ["baffler"], "11.3 10.0 15.9": ["atto"], "1.8 6.4 13.6": ["raibh"], "-4.3 12.6 4.5": ["overhydration"], "-7.1 9.1 7.7": ["artifactual"], "1.7 10.6 11.8": ["curveballer"], "5.5 6.7 18.5": ["indocumentados"], "12.7 8.1 16.1": ["ronde"], "3.2 15.9 4.1": ["protractedly"], "18.2 12.4 11.3": ["finanancial"], "0.8 7.6 5.1": ["properity"], "-1.0 8.3 14.0": ["natatakot"], "5.6 13.9 0.5": ["similarites"], "3.2 -3.1 -3.5": ["groundhandling"], "28.9 11.5 -2.4": ["steelyard"], "7.2 8.0 -3.6": ["postioned"], "-5.9 13.6 1.3": ["advani"], "3.6 11.6 11.7": ["alkynes"], "5.1 0.6 2.1": ["desinger"], "0.5 13.7 12.2": ["dekad"], "9.2 19.2 17.6": ["resprouting"], "18.2 18.6 12.7": ["technosexual"], "5.7 5.0 -5.0": ["alburaq"], "9.9 5.1 19.9": ["jheel"], "5.6 -3.7 0.9": ["annualising"], "18.8 12.2 16.0": ["elephantitis"], "13.8 12.1 9.5": ["reservers"], "25.0 18.5 4.8": ["megacorps"], "11.0 -5.5 22.1": ["poddy"], "-9.1 7.6 5.4": ["hygine"], "-3.1 29.7 -0.3": ["excape"], "11.9 3.4 37.8": ["poutines"], "14.3 10.7 5.4": ["fetishistically"], "9.3 12.5 21.1": ["campanulas"], "16.9 23.4 7.0": ["bullyboys"], "2.8 10.0 9.8": ["punative"], "15.1 -8.1 12.9": ["serviceware"], "5.2 4.2 6.1": ["resouce"], "-2.8 14.4 10.1": ["exerience"], "6.2 -2.3 6.6": ["vorgestellt"], "-0.6 1.6 -1.5": ["arears"], "8.3 19.5 9.4": ["hottness"], "5.3 10.5 4.6": ["ministerships"], "6.5 3.0 0.5": ["gastarbeiter"], "4.7 12.4 1.0": ["itsbusiness"], "11.5 19.4 10.2": ["drudgeries"], "1.5 15.5 5.7": ["sefirot"], "15.5 -6.8 0.3": ["amulti"], "0.4 18.0 1.9": ["theroad"], "5.7 5.8 8.8": ["iptv"], "-3.4 7.5 13.1": ["nonfiscal"], "27.4 8.7 10.0": ["wibbling"], "14.0 16.7 16.1": ["readmore"], "-1.8 10.1 12.6": ["malabsorptive"], "7.8 13.4 21.1": ["ouchie"], "10.2 3.4 9.8": ["condensor"], "1.1 12.4 1.5": ["glycopeptides"], "15.9 0.7 16.4": ["corian"], "13.6 19.0 15.3": ["freakshows"], "-0.2 8.3 12.5": ["silibinin"], "4.5 9.4 9.0": ["fitzgerald"], "9.5 16.4 0.4": ["reconception"], "3.9 11.8 10.4": ["neigborhoods"], "0.1 14.5 8.5": ["homophile"], "-3.7 -5.8 4.2": ["fourweek"], "-8.6 6.1 1.2": ["attempters"], "10.0 2.2 19.1": ["klink"], "8.6 4.7 10.1": ["onths"], "12.0 7.1 18.3": ["theaflavins"], "9.7 14.9 8.8": ["spamware"], "23.5 8.4 28.3": ["whiffle"], "-0.6 9.8 3.0": ["posibilities"], "-6.2 8.2 18.1": ["emas"], "-2.9 7.8 7.5": ["troponins"], "4.3 9.8 -0.4": ["photofinish"], "-2.2 -0.5 14.6": ["ddr"], "-1.0 10.1 19.3": ["indiviudal"], "-1.0 6.9 3.8": ["steerability"], "23.7 13.6 29.8": ["conchas"], "12.9 9.1 -3.5": ["hasalso"], "19.0 14.1 19.8": ["gnarling"], "11.1 -0.1 15.0": ["goldmedal"], "6.8 7.7 9.0": ["suncreams"], "0.2 1.3 11.3": ["teulu"], "13.4 26.1 12.3": ["whimps"], "6.7 29.6 9.7": ["underreacting"], "7.5 4.2 3.9": ["vimeo"], "5.6 13.8 -1.6": ["adapatation"], "12.1 9.2 2.4": ["andcommercial"], "0.4 20.8 1.4": ["equipt"], "4.7 8.3 8.1": ["innng"], "4.3 16.7 10.7": ["policywise"], "7.3 12.1 27.7": ["headpond"], "8.9 16.0 5.5": ["pettily"], "9.6 7.6 35.3": ["alongshore"], "1.2 14.4 -4.0": ["offiicial"], "12.1 12.8 2.6": ["conceptualises"], "3.8 29.1 11.9": ["reductionists"], "2.4 12.4 2.5": ["agst"], "4.7 19.4 5.7": ["khachkars"], "20.6 15.6 24.2": ["untrampled"], "15.7 6.6 5.6": ["poolsides"], "3.6 6.9 8.7": ["suddent"], "9.5 8.6 14.3": ["engergy"], "9.8 3.2 1.7": ["itting"], "15.4 11.2 6.1": ["touchjudge"], "11.9 8.7 23.9": ["broch"], "-3.5 -2.8 4.5": ["cablecasting"], "-2.1 18.1 3.2": ["probies"], "7.5 0.4 5.0": ["agence"], "7.2 4.0 18.5": ["seca"], "12.2 3.7 27.2": ["bulan"], "8.4 5.9 4.9": ["optique"], "4.6 11.6 18.1": ["capsised"], "2.3 -5.0 2.0": ["involing"], "-6.1 -0.1 6.5": ["caesarians"], "6.2 15.2 19.3": ["hawkins"], "2.6 9.8 11.0": ["sumptuary"], "8.5 8.9 19.9": ["ozzy"], "18.0 17.7 9.7": ["errrrr"], "6.4 4.7 15.3": ["hogg"], "1.1 16.2 12.8": ["coprophagia"], "10.4 6.8 6.0": ["blisks"], "12.6 17.3 13.5": ["laydeez"], "16.0 7.0 17.2": ["samulnori"], "2.7 -2.6 5.4": ["spondyloarthritis"], "6.4 25.2 -0.7": ["liberalists"], "6.7 8.8 31.1": ["highbush"], "12.6 16.0 12.1": ["literalized"], "1.0 2.1 0.9": ["theelection"], "-4.6 12.6 1.5": ["counceling"], "7.1 1.8 9.1": ["phenethylamine"], "-5.8 1.7 6.7": ["unco"], "-4.0 3.6 7.7": ["trisomic"], "-2.9 4.1 3.8": ["perovskites"], "19.1 9.7 24.8": ["cutterhead"], "-6.3 -3.6 9.6": ["oligohydramnios"], "3.6 -1.2 -3.8": ["greenpoints"], "18.5 10.0 40.0": ["drummettes"], "4.4 8.8 -0.6": ["homegroup"], "-1.2 -3.7 -2.7": ["recommedations"], "2.6 10.3 0.5": ["reelects"], "14.5 19.0 21.9": ["oomycetes"], "3.2 10.3 0.5": ["expessed"], "16.2 6.2 -1.3": ["officialsaid"], "7.7 13.7 5.8": ["golazo"], "4.7 14.9 12.8": ["improvisors"], "11.6 15.3 8.9": ["hilal"], "14.5 16.4 12.9": ["hemangioblasts"], "-1.2 4.4 9.2": ["juvy"], "8.5 10.0 6.4": ["microphoned"], "1.1 0.0 8.3": ["prochaine"], "7.5 21.7 16.1": ["wunna"], "20.2 3.2 6.0": ["carbonator"], "6.9 6.8 5.3": ["asynchrony"], "0.9 14.0 12.9": ["jursidiction"], "3.6 -1.8 -5.7": ["spok"], "6.9 18.5 14.5": ["taxwise"], "8.7 1.1 11.6": ["minvan"], "1.9 10.7 2.8": ["inprison"], "14.5 8.9 11.8": ["pilers"], "14.1 16.0 10.9": ["preacherman"], "-1.7 19.1 2.1": ["unhelpfulness"], "1.3 16.3 7.5": ["sadaqah"], "12.5 5.4 19.0": ["multiseason"], "5.7 3.0 7.7": ["conve"], "13.6 7.7 10.4": ["displacer"], "7.9 10.5 27.3": ["ghariyals"], "10.7 8.7 45.0": ["bonnethead"], "16.4 -0.2 10.9": ["dollas"], "7.5 -1.3 -4.1": ["affliates"], "5.7 5.8 14.2": ["queda"], "3.9 17.3 12.7": ["gunas"], "-0.6 3.8 9.2": ["occludin"], "5.3 13.9 10.5": ["savingsdiscount"], "3.0 24.2 14.0": ["denoument"], "11.6 12.3 10.3": ["multidevice"], "2.2 2.0 5.9": ["statementsregarding"], "5.8 7.0 12.6": ["wagerer"], "3.1 6.5 7.4": ["ssds"], "13.7 27.4 7.3": ["triedto"], "16.4 15.4 21.9": ["moonflowers"], "14.3 18.8 24.8": ["chocaholic"], "16.8 19.4 32.3": ["bladderwort"], "13.0 10.0 31.3": ["estuarial"], "13.8 5.8 -5.6": ["publicrelations"], "3.0 3.0 0.4": ["converage"], "12.0 12.3 7.1": ["unpackage"], "9.7 8.5 34.0": ["culantro"], "5.1 0.8 9.4": ["aboveaverage"], "-3.3 -6.4 9.6": ["semesterly"], "8.4 4.5 1.9": ["compatiblity"], "-2.7 14.1 5.3": ["satsified"], "12.1 18.3 16.5": ["chemosignals"], "16.6 3.5 9.4": ["quasigovernmental"], "-2.6 3.7 11.1": ["ganoong"], "11.9 2.3 11.8": ["capocannoniere"], "11.7 12.1 12.1": ["extravehicular"], "-9.7 14.0 10.5": ["subsyndromal"], "20.0 6.6 14.1": ["openair"], "5.4 15.2 -0.8": ["imaginativeness"], "9.2 6.0 5.8": ["mediaplayer"], "4.6 9.0 0.8": ["midly"], "6.6 12.0 0.3": ["countervailed"], "-5.9 19.0 0.3": ["encamping"], "-11.9 4.2 4.0": ["concerne"], "8.5 1.7 -4.9": ["managemen"], "6.9 5.3 14.8": ["tkl"], "7.5 14.2 13.5": ["cyberporn"], "13.4 0.1 18.2": ["bioarchaeology"], "6.4 0.6 3.3": ["recategorization"], "12.9 14.6 9.4": ["yesturday"], "3.5 17.6 7.6": ["sissoko"], "-1.6 0.6 13.9": ["nonteachers"], "3.4 18.4 2.9": ["retraumatizing"], "13.0 -3.5 8.8": ["altre"], "-7.4 5.8 9.6": ["hypercalciuria"], "6.0 14.6 10.5": ["downsloping"], "16.3 8.2 3.1": ["hundredsof"], "3.4 5.1 7.9": ["eax"], "7.2 20.4 -2.6": ["duas"], "-2.6 -2.7 1.8": ["megged"], "7.2 9.5 9.3": ["ligases"], "0.6 10.7 -2.9": ["acknowlegement"], "-2.6 6.3 7.1": ["poetesses"], "-2.0 7.9 9.8": ["echinocandins"], "24.9 0.2 -0.6": ["enginemaker"], "7.2 12.3 11.0": ["cabrones"], "20.3 12.6 17.2": ["yech"], "-1.7 15.9 4.2": ["explination"], "7.2 6.0 18.6": ["paterson"], "-1.2 10.5 7.3": ["specif"], "0.3 2.4 7.4": ["reinfusion"], "5.5 8.7 12.8": ["friability"], "-1.9 8.5 16.2": ["unemploy"], "9.5 7.9 13.9": ["monoclonals"], "11.8 18.7 19.1": ["mattocks"], "20.9 12.4 29.0": ["kingsnake"], "3.0 11.1 7.5": ["ptau"], "3.0 14.9 -2.5": ["inconstancies"], "1.9 10.3 2.0": ["picher"], "24.9 12.2 13.5": ["saltiers"], "10.8 12.6 25.2": ["phumdis"], "-0.2 -3.6 -1.1": ["ledby"], "-7.2 -0.9 7.0": ["playwork"], "0.2 18.4 2.8": ["apostleship"], "20.6 14.2 13.4": ["tweenager"], "9.9 17.6 10.0": ["griper"], "9.1 13.8 21.6": ["jetskier"], "4.2 2.4 4.5": ["cifs"], "15.8 9.4 9.7": ["crackberries"], "-0.2 20.3 3.8": ["preasure"], "5.2 16.0 10.3": ["gauntness"], "13.2 14.4 23.0": ["daytripping"], "-3.8 -1.5 -0.2": ["vention"], "-0.3 8.5 6.1": ["parameterised"], "8.7 8.2 15.7": ["kaali"], "4.0 12.8 10.5": ["repressurization"], "7.8 0.5 17.5": ["sheerer"], "1.4 4.1 6.4": ["bagatelles"], "5.3 11.2 5.6": ["everyon"], "-5.6 8.1 4.1": ["hepatotoxic"], "2.3 -4.7 0.9": ["basetball"], "10.4 8.7 27.5": ["borshch"], "13.1 6.2 10.2": ["overloud"], "5.5 5.1 8.2": ["wetroom"], "3.3 -1.9 30.7": ["romas"], "6.1 6.6 17.7": ["smelliness"], "9.8 20.4 11.7": ["perilousness"], "3.8 10.7 -5.6": ["groupof"], "5.7 11.2 14.2": ["uru"], "-5.3 10.0 5.5": ["obituarist"], "6.8 7.3 -2.3": ["operatio"], "12.1 12.0 4.2": ["stn"], "9.3 16.7 18.3": ["preditors"], "5.5 4.5 9.9": ["casos"], "2.7 11.2 5.5": ["deglamorised"], "8.7 27.2 -2.6": ["promulgators"], "6.1 18.5 4.6": ["atomism"], "-1.6 19.2 8.8": ["whatis"], "-1.5 5.9 4.2": ["highfaluting"], "14.8 23.7 7.8": ["revenants"], "-1.4 11.7 12.5": ["hurriedness"], "18.9 3.9 20.6": ["varicolored"], "2.3 12.0 9.8": ["rebind"], "20.7 13.2 14.2": ["huuuge"], "9.7 10.2 3.1": ["tarmaced"], "4.3 8.2 9.5": ["zenana"], "1.9 2.4 5.7": ["multiasset"], "-3.4 8.9 7.2": ["syair"], "7.1 3.5 17.5": ["zhe"], "11.6 16.8 16.9": ["breeded"], "13.7 5.1 7.2": ["formato"], "12.5 1.8 14.7": ["gagne"], "1.8 5.3 3.1": ["compunded"], "16.5 3.4 9.9": ["glummest"], "19.6 2.7 6.6": ["hardward"], "-6.3 6.5 5.0": ["consultatively"], "6.4 12.5 12.6": ["roofied"], "11.6 13.9 12.9": ["transite"], "2.4 10.6 14.1": ["backstretches"], "8.4 11.1 16.0": ["firefigthers"], "6.8 10.7 12.9": ["aspera"], "3.5 11.5 3.4": ["saffronise"], "-4.6 2.5 -1.9": ["distt"], "11.3 16.6 3.9": ["messenging"], "14.9 9.1 23.7": ["charticle"], "-4.5 12.3 14.4": ["headball"], "23.7 0.6 7.8": ["floatations"], "12.9 9.2 19.2": ["nanopolymer"], "27.0 -3.3 7.4": ["pharmacutical"], "8.0 6.2 25.5": ["whalewatching"], "8.4 5.6 17.5": ["fiona"], "1.0 3.7 4.3": ["inearly"], "2.3 15.0 7.2": ["gaalis"], "9.9 14.0 20.7": ["lazarette"], "3.6 -3.2 1.3": ["conforme"], "16.8 13.9 22.1": ["hamentaschen"], "10.8 12.2 9.4": ["imago"], "6.0 3.4 12.0": ["dmtu"], "-1.3 0.8 4.4": ["irreproachably"], "15.5 -6.1 7.6": ["applaudes"], "6.1 3.7 12.6": ["rhaid"], "9.7 8.1 3.5": ["smilar"], "16.1 5.9 5.5": ["quipment"], "-5.9 7.2 8.1": ["overestimations"], "8.0 10.8 13.5": ["chismis"], "16.3 4.1 12.7": ["phrenologists"], "-3.0 23.2 10.7": ["redemptively"], "-0.4 1.8 7.4": ["monocrotophos"], "-1.2 1.8 15.9": ["alaga"], "10.4 11.1 2.7": ["tippees"], "-6.4 1.0 7.8": ["aminotransferase"], "14.8 2.1 8.9": ["curviness"], "5.3 11.2 21.0": ["dessication"], "-2.5 12.6 9.8": ["interstitium"], "11.2 6.9 34.4": ["squawfish"], "3.3 2.4 11.4": ["beamformer"], "9.5 30.9 11.2": ["untermensch"], "4.5 20.7 13.2": ["naiive"], "7.2 15.1 9.8": ["antilabor"], "11.1 3.7 20.7": ["leatherwood"], "18.2 14.4 19.1": ["discodermolide"], "13.7 10.1 4.8": ["itss"], "-0.7 5.6 16.1": ["inaasahan"], "3.0 12.9 12.0": ["samy"], "2.6 1.0 9.2": ["naturang"], "3.3 8.8 4.3": ["officielle"], "15.1 14.8 16.6": ["pentacles"], "8.9 30.1 8.9": ["dangerious"], "2.8 16.0 14.5": ["dicy"], "18.3 7.7 12.7": ["advocaat"], "6.3 4.8 2.9": ["medispa"], "16.4 -2.8 10.5": ["venta"], "10.3 -0.5 4.5": ["placename"], "5.8 16.5 24.8": ["awamori"], "4.0 5.9 4.5": ["underserve"], "1.2 26.4 8.3": ["dunya"], "1.8 14.5 5.4": ["chamar"], "-5.9 15.5 3.1": ["traumatisation"], "-3.1 0.2 3.9": ["aggrevating"], "-6.9 10.7 5.4": ["stess"], "-1.0 19.7 6.7": ["dialoge"], "-0.1 8.1 18.0": ["julius"], "4.1 11.6 21.8": ["interplanting"], "4.1 10.6 1.9": ["ifbyphone"], "6.9 7.9 9.8": ["teez"], "4.0 -1.1 6.5": ["avulsions"], "-3.9 10.6 -2.0": ["quantifier"], "10.7 11.3 6.2": ["faultiness"], "-5.3 13.6 5.7": ["insecured"], "6.6 -2.5 -6.3": ["exectutive"], "3.4 -0.1 6.8": ["babalawos"], "11.8 26.6 21.8": ["ideogram"], "-1.0 -0.1 9.8": ["perscribed"], "6.6 5.4 4.9": ["lott"], "3.5 12.9 7.9": ["awaaz"], "10.2 23.2 21.7": ["righto"], "12.4 6.2 8.9": ["computor"], "-4.2 0.9 6.8": ["salestax"], "11.0 27.5 11.8": ["dynasts"], "7.4 12.5 16.0": ["foremother"], "12.7 15.1 15.1": ["whelm"], "-0.1 8.0 0.6": ["prophetical"], "4.6 8.5 23.5": ["freedive"], "-1.6 -7.7 5.2": ["inthree"], "18.2 1.7 10.0": ["eqivalent"], "-11.6 10.2 6.6": ["linemaker"], "15.9 10.5 23.0": ["tweety"], "14.5 2.4 14.8": ["nacimiento"], "11.7 4.1 8.6": ["mbtu"], "4.1 2.0 1.7": ["twodays"], "5.9 7.5 10.6": ["ankyrin"], "1.0 9.1 10.9": ["onepoint"], "16.2 4.1 17.1": ["mobius"], "10.2 3.9 4.9": ["namedropped"], "-0.4 6.4 16.0": ["tawo"], "15.5 16.7 15.5": ["shitbag"], "7.3 15.8 11.6": ["metalloproteinases"], "2.0 -2.2 9.1": ["atre"], "9.5 3.7 8.8": ["congres"], "9.2 16.7 4.3": ["disloyally"], "9.7 9.6 8.3": ["breastbones"], "7.2 2.9 3.5": ["unitranche"], "2.7 7.4 6.9": ["informationand"], "-5.2 0.8 4.6": ["dinucleotide"], "3.3 4.2 3.8": ["unserer"], "5.8 3.3 3.9": ["enterd"], "15.2 25.2 18.1": ["maenads"], "2.9 13.1 3.8": ["equilibrating"], "17.0 -2.0 7.2": ["ebita"], "8.4 10.4 5.3": ["curva"], "20.6 11.2 15.6": ["skywalking"], "5.2 -1.1 14.4": ["ridley"], "9.0 9.2 14.8": ["singulated"], "10.2 18.1 12.1": ["theur"], "5.8 9.4 -0.5": ["srike"], "1.1 11.7 8.4": ["lways"], "11.1 1.0 15.2": ["amblers"], "-0.8 8.1 4.3": ["restrike"], "5.7 15.6 -2.5": ["metted"], "17.3 -0.8 19.3": ["scien"], "-0.2 9.7 7.2": ["soliloquizing"], "5.1 11.6 2.9": ["ectodomain"], "2.1 7.3 3.9": ["palsies"], "17.4 8.4 1.6": ["cartpath"], "2.1 14.8 7.0": ["toshow"], "15.4 19.7 23.3": ["poontang"], "3.3 18.0 7.7": ["deposal"], "11.8 5.1 12.1": ["drumkits"], "12.4 3.7 5.9": ["exchangable"], "12.2 27.8 6.7": ["nukular"], "11.7 15.5 2.0": ["camcord"], "6.1 29.0 12.8": ["compassions"], "1.4 5.7 6.3": ["quizz"], "3.2 3.8 8.9": ["pentathalon"], "12.6 16.0 5.7": ["mytho"], "7.0 11.5 21.3": ["shakshuka"], "12.2 10.5 15.2": ["iceholes"], "6.9 1.4 14.2": ["macrodiamond"], "0.6 9.7 9.3": ["sce"], "9.7 7.0 15.8": ["fannypack"], "7.3 11.5 13.7": ["pleasureable"], "6.5 26.0 13.2": ["finess"], "5.0 10.7 7.8": ["bumfuzzled"], "8.5 3.5 16.2": ["panjabi"], "1.8 13.3 3.0": ["cavilling"], "6.6 8.8 10.8": ["strikebreaker"], "15.2 11.9 34.1": ["birdseye"], "24.7 2.5 12.8": ["tubbies"], "17.8 3.3 23.9": ["nougatine"], "22.5 -3.5 14.3": ["indusrty"], "2.7 3.1 7.7": ["csc"], "9.0 18.9 2.1": ["anhydrase"], "1.4 15.0 4.4": ["kiths"], "24.5 11.1 14.3": ["browing"], "15.5 -2.4 9.4": ["sume"], "12.1 13.6 23.8": ["feedin"], "9.7 1.1 6.8": ["incrased"], "-5.7 2.0 -2.9": ["mylene"], "3.1 12.9 16.0": ["memba"], "10.9 3.6 47.1": ["langostinos"], "7.9 12.6 12.4": ["downflow"], "10.5 24.9 4.0": ["maximisers"], "15.6 9.4 14.7": ["waggin"], "16.4 17.0 9.8": ["blatting"], "10.7 23.3 14.8": ["hotbar"], "0.5 -2.8 8.3": ["amser"], "16.0 24.2 14.1": ["horsewhips"], "2.0 12.1 14.3": ["preestablished"], "3.4 9.0 8.3": ["backpeddle"], "15.2 6.9 5.8": ["thermosolar"], "5.2 -2.3 -2.7": ["jml"], "13.6 12.4 7.4": ["retape"], "15.5 8.0 15.9": ["saling"], "9.5 3.8 22.3": ["hooka"], "-6.3 15.8 2.8": ["nazm"], "1.7 6.1 -4.0": ["andprovide"], "14.5 15.6 8.0": ["downspin"], "0.7 -7.4 -1.7": ["contribut"], "10.8 15.9 12.6": ["goalframe"], "-5.4 8.2 -3.8": ["investigat"], "-1.5 -3.6 6.6": ["energyefficiency"], "-3.1 25.6 5.4": ["clanism"], "6.6 0.5 -2.1": ["fdi"], "20.9 1.8 -2.8": ["instituitions"], "1.0 -1.5 5.7": ["ncrease"], "4.3 -4.1 7.2": ["alumi"], "1.7 10.0 13.3": ["laddishness"], "2.7 5.5 -2.7": ["toestablish"], "-1.6 -5.3 10.9": ["licen"], "1.1 4.4 5.7": ["redemarcation"], "-2.5 3.9 10.4": ["serbisyo"], "6.6 5.4 -1.9": ["coperation"], "5.6 24.5 -0.8": ["destablisation"], "12.3 6.0 14.6": ["gubment"], "11.9 10.3 34.5": ["greenshank"], "6.4 8.3 4.2": ["sheikha"], "-3.7 26.7 3.8": ["efforted"], "3.5 25.4 11.1": ["distractedness"], "8.6 9.7 30.0": ["oakum"], "11.0 27.1 3.2": ["energisers"], "5.3 -6.2 6.1": ["theproduct"], "8.3 3.1 7.9": ["laparoscopes"], "6.5 10.3 17.8": ["exudation"], "18.5 4.5 23.9": ["greenheart"], "12.9 12.7 28.4": ["hund"], "2.2 -1.5 11.0": ["beautillion"], "9.4 9.6 9.6": ["knapp"], "14.0 16.9 8.4": ["entwinement"], "5.1 8.7 6.2": ["probl"], "3.5 3.0 13.0": ["squaregaiters"], "6.9 10.4 7.7": ["cessna"], "9.1 -0.6 4.5": ["theinvestment"], "16.8 10.6 4.7": ["spewer"], "11.0 5.1 15.6": ["taille"], "-4.5 15.0 4.1": ["preventible"], "7.2 23.2 6.9": ["noboby"], "4.4 3.2 0.2": ["blabla"], "8.4 8.0 -4.1": ["cossets"], "20.4 13.6 21.3": ["plantlike"], "12.1 8.0 7.7": ["geworden"], "12.1 8.5 25.8": ["housepainters"], "5.4 12.8 12.6": ["copr"], "3.2 11.0 17.0": ["diara"], "11.3 11.9 8.7": ["bobsleighing"], "12.7 1.4 18.4": ["pegger"], "20.4 15.9 12.0": ["superstorms"], "-5.4 26.0 0.9": ["effaces"], "-6.7 9.2 5.6": ["ataxias"], "19.6 20.9 12.5": ["vapourise"], "4.3 14.5 2.6": ["intransparent"], "21.1 21.7 16.9": ["nosily"], "4.9 1.5 13.5": ["boyle"], "9.1 -1.6 7.0": ["cyberstates"], "7.5 14.2 14.2": ["vechiles"], "-5.8 11.2 -3.6": ["ensurethat"], "0.7 7.4 8.7": ["pyoderma"], "16.1 2.5 2.6": ["keypunch"], "4.9 17.7 6.3": ["languge"], "9.4 11.4 15.4": ["maja"], "8.0 -0.3 19.4": ["leafiness"], "5.8 4.1 29.7": ["handfishing"], "11.8 22.3 8.3": ["moralistically"], "-3.0 30.7 4.0": ["endue"], "7.1 1.0 3.9": ["rebundled"], "3.7 5.7 11.3": ["propulsor"], "3.7 -4.7 7.5": ["doubl"], "8.8 2.3 11.6": ["cappings"], "11.6 10.1 13.8": ["mams"], "10.4 11.1 22.3": ["bennie"], "3.1 5.8 3.1": ["requ"], "9.2 5.1 38.7": ["confits"], "1.7 8.9 20.4": ["preppier"], "-1.6 9.2 1.4": ["cablegram"], "12.8 6.4 18.6": ["redmond"], "-3.3 17.9 11.4": ["neuropilin"], "5.9 5.5 4.9": ["theprovince"], "11.0 12.5 14.4": ["ecchi"], "12.8 14.6 13.0": ["olly"], "6.6 3.6 9.1": ["maglia"], "19.4 1.9 9.8": ["suona"], "4.3 -2.1 9.7": ["dce"], "2.4 6.6 6.9": ["kevindonahue"], "15.1 -0.1 15.3": ["hootchy"], "15.6 13.6 18.4": ["untipped"], "5.3 19.9 15.4": ["campfest"], "13.4 9.1 13.1": ["selvages"], "15.1 1.3 17.7": ["ammoniated"], "12.0 6.4 29.8": ["vacherin"], "-6.0 -1.2 0.3": ["underattended"], "3.2 15.8 -1.4": ["inspring"], "18.4 18.6 8.4": ["yabbering"], "3.5 9.9 17.7": ["perserved"], "2.1 -0.8 5.1": ["apprized"], "8.4 3.7 10.8": ["geomarkets"], "1.8 13.8 7.6": ["masculinised"], "-4.5 3.6 -2.6": ["partcipating"], "-2.7 -6.7 4.1": ["accor"], "27.7 5.1 5.9": ["manufacuring"], "-4.5 13.5 5.2": ["atuned"], "6.4 9.6 5.7": ["applic"], "7.8 8.6 7.7": ["childred"], "8.9 4.1 9.0": ["bjorn"], "17.2 13.7 14.3": ["nannyish"], "8.7 12.3 19.6": ["mada"], "8.7 13.0 8.7": ["mlevy"], "-6.2 -6.8 -2.3": ["competit"], "6.9 13.8 11.1": ["reachstackers"], "7.7 9.1 10.8": ["folf"], "9.7 20.5 17.3": ["hippee"], "6.7 17.7 18.6": ["subtilis"], "3.5 7.4 5.2": ["zakaat"], "8.6 24.2 1.4": ["disintegrative"], "10.8 11.8 16.2": ["burgermeister"], "1.2 14.0 14.8": ["wac"], "0.8 10.9 -1.6": ["antifibrotic"], "16.5 3.2 15.1": ["vivariums"], "-1.8 18.0 -0.5": ["atempts"], "-9.0 -3.6 4.9": ["duhn"], "3.8 -2.2 11.9": ["swydd"], "3.6 -2.7 -5.5": ["conceptualiser"], "12.8 6.5 13.0": ["mineros"], "1.8 7.5 0.3": ["imprimaturs"], "10.3 6.2 5.4": ["signifigantly"], "15.4 6.5 25.2": ["chikoo"], "16.2 18.4 12.0": ["duper"], "17.0 20.7 23.0": ["encysted"], "5.7 15.4 9.4": ["bcome"], "3.8 21.5 4.7": ["gased"], "-6.2 25.3 0.5": ["dutybound"], "4.0 20.4 8.2": ["unrefueled"], "9.7 32.9 7.1": ["terrror"], "7.6 10.6 11.1": ["devocalized"], "11.3 6.4 -3.7": ["eorge"], "10.1 2.8 10.8": ["firestop"], "1.4 2.8 10.1": ["deutschland"], "6.0 -4.5 -2.0": ["royalblue"], "10.8 22.9 16.4": ["schoolground"], "-1.6 7.5 8.5": ["remeasurements"], "18.1 12.8 11.9": ["curtseyed"], "9.6 15.3 16.8": ["lizzy"], "7.4 9.6 15.3": ["balletomane"], "9.6 6.9 13.7": ["gome"], "1.3 6.7 12.5": ["aminophylline"], "4.7 15.4 14.9": ["propertyless"], "5.7 23.4 -1.2": ["ritain"], "5.8 -0.3 17.7": ["opisina"], "12.8 0.1 8.1": ["teamis"], "-10.7 2.1 -1.7": ["organizaiton"], "2.9 3.2 5.5": ["aktuellen"], "10.6 22.3 21.1": ["lotas"], "4.9 17.8 12.8": ["credentialism"], "6.9 18.3 19.7": ["execpt"], "8.9 18.3 17.7": ["quibblers"], "6.2 -3.5 0.5": ["monofill"], "5.9 8.2 14.8": ["antilitter"], "4.2 9.6 14.3": ["uff"], "9.4 11.8 11.7": ["lusters"], "1.0 10.2 10.0": ["eliteness"], "2.7 11.0 7.4": ["arties"], "-10.5 -1.4 -2.1": ["mni"], "13.1 18.1 16.3": ["underlaying"], "2.4 5.8 17.1": ["hyperkeratosis"], "-1.1 13.3 8.5": ["dreamwork"], "8.8 4.1 -1.5": ["memor"], "-0.1 10.8 15.1": ["sericitization"], "2.0 16.4 3.5": ["angiostatin"], "0.1 11.2 6.3": ["sneijder"], "13.4 16.5 29.9": ["labne"], "17.9 1.0 11.4": ["noveau"], "2.0 7.4 5.2": ["malapposition", "pulsewidth"], "10.5 12.9 28.5": ["palmyrah"], "-1.1 12.4 9.7": ["ssb"], "24.0 8.7 27.5": ["limburger"], "21.3 20.7 36.4": ["blobfish"], "13.6 13.6 18.9": ["stuntin"], "2.0 4.7 -0.2": ["naronapride"], "21.6 8.7 4.9": ["undergeared"], "13.0 35.9 3.5": ["opressive"], "-1.2 7.7 5.9": ["auricle"], "-4.2 8.2 -4.3": ["admiited"], "-5.0 21.5 11.0": ["findeth"], "11.6 14.5 22.0": ["lifestock"], "4.9 5.1 13.9": ["underinsuring"], "16.4 7.3 20.0": ["chinning"], "10.5 5.3 9.2": ["azulgrana"], "0.4 -3.5 8.8": ["gbs"], "9.6 3.1 16.1": ["carnauba"], "11.8 9.1 10.6": ["fustiness"], "9.4 7.1 17.3": ["rudraksh"], "6.0 14.1 2.7": ["nonjusticiable"], "6.8 45.5 9.2": ["dropships"], "15.8 4.9 7.9": ["supertram"], "9.5 6.4 12.9": ["clamminess"], "3.4 11.7 15.4": ["quickdraw"], "10.7 6.0 9.3": ["underpromoted"], "19.7 15.0 12.4": ["showgoer"], "17.6 16.4 21.9": ["flagellates"], "1.0 18.1 25.2": ["zzzs"], "19.0 20.9 35.8": ["chunkers"], "22.6 18.6 21.4": ["fangless"], "14.7 1.8 6.3": ["linx"], "3.5 18.3 -5.5": ["partizan"], "18.9 20.5 11.2": ["minifigure"], "12.0 9.0 15.6": ["lankiness"], "7.7 -7.5 7.1": ["lago"], "7.9 13.0 1.2": ["denen"], "15.3 21.0 21.9": ["gaspingly"], "7.5 2.9 26.4": ["harira"], "-7.2 2.6 2.5": ["dialyse"], "12.1 13.7 9.7": ["glimps"], "-0.1 2.5 2.5": ["triplicates"], "8.3 11.0 -2.3": ["toksee"], "1.5 3.1 11.0": ["janice"], "4.5 -4.5 12.0": ["retaurant"], "4.0 -1.2 7.0": ["lihs"], "-3.7 11.1 6.9": ["intercommunion"], "16.2 17.0 13.0": ["swagman"], "3.9 10.7 13.2": ["mestizaje"], "-7.3 2.8 -2.5": ["ecretary"], "0.5 21.9 8.7": ["necessarly"], "2.9 20.9 7.7": ["akhbar"], "12.9 11.2 10.5": ["semiautonomy"], "8.1 20.3 -0.5": ["usedin"], "21.0 16.3 20.1": ["martonas"], "0.4 -0.3 13.6": ["yos"], "13.2 15.2 5.5": ["blogfather"], "-9.8 -4.6 7.8": ["prefile"], "11.2 14.8 50.5": ["porbeagles"], "14.1 6.4 13.2": ["freakonomics"], "11.4 -3.5 14.1": ["uridashis"], "12.4 6.9 4.9": ["suckfest"], "-5.4 11.4 19.0": ["kahirapan"], "2.0 2.3 13.1": ["saidt"], "7.2 9.7 3.8": ["kaval"], "10.1 11.4 9.4": ["multipiece"], "1.6 15.9 19.9": ["satvik"], "1.8 -3.9 15.2": ["guro"], "8.0 0.5 9.7": ["ramsac"], "-4.0 5.5 12.5": ["butterfliers"], "2.9 4.5 8.3": ["ppbv"], "11.1 22.0 9.6": ["carceral"], "12.2 11.2 28.9": ["dickcissel"], "5.0 3.8 16.6": ["neprilysin"], "8.0 6.8 13.4": ["lowpoints"], "23.6 36.2 16.2": ["xenomorphs"], "8.4 14.3 5.9": ["benchmarkers"], "14.4 2.8 33.1": ["rissole"], "5.6 34.6 11.0": ["unwinable"], "7.5 -1.3 10.9": ["doppio"], "3.1 4.7 5.4": ["attrib"], "5.5 14.3 9.4": ["keyman"], "10.1 7.9 16.1": ["plumetting"], "13.2 0.4 5.0": ["sublandlord"], "12.4 13.4 17.0": ["uncomfy"], "3.0 4.0 8.3": ["micromanipulation"], "10.2 7.6 12.9": ["moneyback"], "3.5 9.2 7.4": ["assimilable"], "19.4 13.1 20.2": ["untoned"], "9.2 8.2 33.5": ["jalepenos"], "10.3 15.3 15.1": ["unploughed"], "10.5 12.0 13.1": ["whis"], "-1.7 5.6 7.3": ["angavastram"], "26.8 -0.9 14.0": ["balloonlike"], "0.6 11.9 4.3": ["corper"], "12.3 12.4 25.2": ["kelley"], "11.5 6.3 8.0": ["bext"], "-9.7 7.5 10.1": ["thelaw"], "-1.7 17.9 5.7": ["licitly"], "-5.3 2.8 6.2": ["pheochromocytomas"], "8.2 11.8 10.4": ["replug"], "8.7 16.9 3.7": ["formulistic"], "9.4 10.5 5.9": ["masr"], "8.3 5.0 8.6": ["polyaspartic"], "3.4 3.5 14.9": ["tshechu"], "11.7 -5.1 17.8": ["palletization"], "2.7 16.9 10.3": ["laxly"], "17.8 13.0 38.7": ["crinoid"], "23.6 18.8 21.5": ["weathercock"], "0.5 6.5 11.1": ["solventborne"], "4.1 6.2 8.8": ["streetbikes"], "2.5 9.1 5.1": ["secys"], "7.2 13.2 10.9": ["pichichi"], "17.2 4.6 33.1": ["pome"], "2.8 13.5 4.1": ["gaucherie"], "-1.6 11.3 8.5": ["hotwalkers"], "17.9 9.0 7.5": ["pissoirs"], "10.0 13.2 30.4": ["kiore"], "2.7 14.5 3.6": ["managerialist"], "18.9 9.5 7.2": ["featurs"], "-5.3 8.8 2.1": ["chanc"], "20.3 14.8 4.7": ["warners"], "-4.2 3.2 14.7": ["mahigit"], "8.3 2.9 2.7": ["partnerhip"], "-1.8 10.4 10.1": ["sabhi"], "-0.7 -6.0 -7.4": ["hasreceived"], "8.3 2.8 15.8": ["joka"], "3.3 1.3 3.7": ["dicembre"], "25.9 28.0 10.5": ["prodder"], "4.9 -1.7 10.6": ["capitale"], "3.3 11.2 14.5": ["shtik"], "8.7 12.6 11.5": ["phrasal"], "4.0 -0.6 3.8": ["ebilling"], "11.8 4.1 28.5": ["linguisa"], "1.4 23.3 9.2": ["valorizes"], "7.1 4.1 7.1": ["readmits"], "26.8 4.8 -1.0": ["compamy"], "-3.6 10.7 2.4": ["contemp"], "15.2 25.3 17.9": ["puzzlements"], "-4.0 13.7 9.8": ["versification"], "13.8 10.2 11.4": ["blastings"], "22.6 12.6 9.0": ["hoaxsters"], "13.0 0.8 12.5": ["windown"], "9.5 16.0 0.9": ["bonyads"], "7.2 4.5 12.1": ["jerkier"], "14.0 7.6 26.1": ["fondants"], "2.0 -2.0 -1.6": ["regulat"], "6.0 -0.2 7.9": ["jih"], "1.7 12.2 11.1": ["disaggregates"], "11.3 14.3 10.0": ["godess"], "8.2 -4.8 5.0": ["twomonths"], "20.2 23.7 6.2": ["unsportingly"], "-1.4 1.7 10.8": ["kalpanaswaras"], "-1.2 19.1 9.3": ["madhesis"], "1.1 10.6 23.1": ["blufflands"], "7.8 6.4 26.4": ["pepperiness"], "7.3 15.5 15.9": ["backspacing"], "2.2 24.8 3.9": ["persuation"], "-5.6 6.1 2.0": ["sations"], "-7.7 4.0 -0.8": ["oversighted"], "7.6 11.9 14.6": ["donno"], "6.4 10.9 -0.4": ["nown"], "17.5 14.0 27.5": ["cowpies"], "-2.9 5.3 4.1": ["arra"], "4.6 11.9 22.0": ["shortstack"], "6.8 3.0 7.7": ["nitely"], "-3.5 6.0 3.1": ["infraspinatus"], "6.9 22.7 4.6": ["exhortatory"], "17.8 22.5 16.8": ["legsweep"], "-0.6 -1.1 5.4": ["octanol"], "12.7 26.7 21.3": ["overplant"], "5.1 9.9 -1.0": ["affiar"], "6.6 9.8 1.5": ["hydal"], "2.1 23.6 3.8": ["postmoderns"], "-2.9 5.5 9.3": ["kasong"], "0.0 11.9 6.4": ["alphabetization"], "10.5 2.6 6.2": ["bestanden"], "8.9 17.1 9.0": ["ganster"], "11.8 1.2 9.1": ["rall"], "6.1 0.7 9.2": ["desarrollo"], "1.3 5.0 5.5": ["pthalates"], "3.6 -1.3 -1.6": ["appproved"], "5.0 8.5 10.0": ["mohamed"], "13.7 4.0 27.3": ["ecolabelling"], "-1.6 5.3 0.9": ["machzor"], "4.9 8.1 10.0": ["mangina"], "9.6 17.1 11.3": ["yawping"], "14.7 7.2 10.6": ["stripteasers"], "9.0 4.1 7.8": ["estrellas"], "11.4 1.5 -0.5": ["blns"], "9.2 0.3 0.9": ["posta"], "14.5 10.4 1.9": ["fleeted"], "5.6 5.3 10.4": ["achkan"], "-5.4 2.3 5.5": ["reaccredit"], "1.1 10.6 1.2": ["refrence"], "-5.2 10.3 4.6": ["nonsubstantive"], "-8.4 6.1 7.0": ["antiandrogens"], "8.7 13.0 -0.8": ["themedia"], "19.7 15.0 25.1": ["polynesian"], "-3.7 3.9 6.1": ["fascicles"], "-1.3 11.3 5.9": ["unacademic"], "-2.4 25.3 6.6": ["eit"], "-6.3 5.8 5.3": ["alent"], "0.3 5.1 3.6": ["reentrant"], "10.0 10.7 14.1": ["kamrom"], "22.2 5.1 1.1": ["planemaking"], "11.9 7.9 7.7": ["secondbest"], "9.0 -7.3 5.3": ["ajor"], "-4.5 12.4 7.4": ["naani"], "23.0 6.7 10.2": ["gasometers"], "5.1 12.2 3.7": ["rephotographed"], "15.6 10.1 25.8": ["cabazon"], "6.3 9.8 6.2": ["splenocytes"], "11.2 1.9 9.1": ["glauconite"], "6.3 18.4 11.3": ["homesickalien"], "14.1 10.6 23.3": ["pog"], "3.3 7.4 15.1": ["detectably"], "2.5 -1.4 9.6": ["idioma"], "12.2 10.6 4.5": ["obsoleting"], "24.1 9.5 18.9": ["tangram"], "-0.7 9.0 -0.2": ["refus"], "16.2 15.3 -0.1": ["neutraliser"], "16.6 10.2 21.0": ["loli"], "-11.4 -6.2 0.3": ["perinatologists"], "10.4 10.9 11.4": ["noncomedogenic"], "9.9 7.3 41.1": ["kelaguen"], "14.1 18.8 8.1": ["greedhead"], "7.6 -4.6 6.9": ["dominic"], "6.0 -1.7 7.4": ["smoggier"], "7.1 -0.7 5.5": ["meilleurs"], "3.6 -4.4 1.6": ["comptes"], "-3.5 1.3 20.7": ["daghan"], "2.1 8.3 20.6": ["yedoma"], "3.2 -3.0 17.0": ["tumba"], "6.9 5.4 6.2": ["taraweeh"], "-9.3 -2.0 4.6": ["troo"], "3.1 1.6 1.2": ["jobsearch"], "16.8 -2.0 -0.8": ["mhealth"], "-2.5 11.6 8.2": ["radiopacity"], "3.9 17.7 4.8": ["ingratiates"], "-7.5 17.9 2.1": ["eldership"], "-8.3 -9.2 0.5": ["poiints"], "2.3 23.7 8.4": ["fustrating"], "5.6 14.1 -0.4": ["userscript"], "16.0 5.0 15.5": ["tramworks"], "3.5 22.3 12.5": ["highmarking"], "-2.7 16.0 3.8": ["cellhouse"], "15.1 -5.6 -0.8": ["providng"], "6.8 9.6 19.5": ["donny"], "11.2 7.9 14.5": ["rike"], "-3.3 9.5 6.0": ["udner"], "-5.3 11.4 -0.3": ["pursuable"], "3.4 7.3 7.3": ["undisplayed"], "11.4 9.3 4.9": ["faultily"], "9.0 10.0 7.3": ["underfilling"], "11.4 13.4 9.1": ["masculinisation"], "4.0 -0.8 1.4": ["officiellement"], "9.3 21.8 5.8": ["messagers"], "10.8 3.4 6.0": ["vancouversun"], "-0.7 25.7 4.0": ["perjuring"], "9.4 -2.7 16.8": ["tahoe"], "7.2 10.0 14.6": ["maith"], "5.7 26.3 9.6": ["intifadeh"], "23.1 16.6 15.0": ["blooze"], "20.1 16.9 8.9": ["wanabe"], "9.4 -1.7 -0.5": ["collaterised"], "12.6 1.7 37.4": ["plaintain"], "8.6 11.5 21.4": ["stonecutting"], "1.0 -1.1 5.8": ["redu"], "6.6 0.5 6.5": ["nterest"], "3.9 12.7 11.8": ["doleouts"], "-2.3 1.7 10.1": ["etta"], "-9.6 2.2 4.4": ["euthymic"], "2.4 10.6 0.7": ["electret"], "2.0 1.2 -2.2": ["applicatons"], "14.6 13.6 26.2": ["mooners"], "8.8 -1.2 14.8": ["ikats"], "2.5 12.1 11.2": ["multigenic"], "-0.1 4.6 14.4": ["multisporter"], "12.6 11.9 27.4": ["oviposition"], "6.8 -1.2 36.1": ["bistecca"], "2.8 2.5 16.4": ["unearmarked"], "0.6 0.6 3.7": ["operati"], "10.6 -2.0 4.6": ["scalebacks"], "-0.4 2.9 20.7": ["hanh"], "10.5 17.5 22.5": ["murga"], "4.8 5.8 8.7": ["themiddle"], "-7.4 16.1 5.2": ["mha"], "6.1 1.6 9.9": ["transtibial"], "7.2 10.7 10.3": ["daughterly"], "20.2 7.8 28.0": ["dacquoise"], "7.7 -0.7 10.9": ["openend"], "-3.4 4.9 12.2": ["kausap"], "17.5 23.1 20.7": ["creepies"], "9.9 9.7 9.5": ["classement"], "-2.7 10.6 1.8": ["interpretability"], "9.9 12.1 8.2": ["noncoverage"], "10.8 15.6 6.3": ["carhaul"], "1.0 4.4 20.5": ["kahu"], "-1.2 11.7 17.4": ["sunbreaks"], "-1.4 5.2 13.5": ["contangoed"], "11.5 11.9 16.2": ["cermet"], "14.7 14.9 17.6": ["hobbie"], "5.3 11.9 7.6": ["unproductiveness"], "1.9 5.5 6.4": ["sieben"], "-1.3 9.2 11.2": ["spotchecks"], "9.9 14.6 7.3": ["gahmen"], "15.0 0.1 15.4": ["tussen"], "9.8 1.2 8.4": ["fonction"], "16.3 7.2 17.7": ["presepio"], "-10.0 8.5 4.2": ["ridealongs"], "-2.4 17.8 7.6": ["demythologizing"], "-4.2 -1.9 12.9": ["mornig"], "4.7 16.6 12.4": ["humbugging"], "-1.3 12.1 8.0": ["regressiveness"], "10.3 6.4 11.1": ["cabinetisation"], "5.2 1.5 11.3": ["papeles"], "-0.9 9.6 13.8": ["kavita"], "1.0 8.2 8.1": ["sapa"], "8.6 3.0 17.3": ["jarocho"], "10.2 5.7 5.2": ["calderon"], "15.3 10.8 19.1": ["backloop"], "9.1 15.1 11.1": ["comedowns"], "26.9 13.7 12.5": ["bauhinia"], "14.6 12.7 13.0": ["quasicrystalline"], "18.4 -1.2 7.5": ["retrofitters"], "9.5 10.0 -1.4": ["petawatt"], "3.3 0.8 0.2": ["operatons"], "4.4 15.2 12.9": ["loran"], "10.3 1.2 8.6": ["adoptors"], "15.8 2.8 7.1": ["diamondoids"], "11.5 15.8 10.5": ["undersupervised"], "10.5 7.7 19.7": ["chickees"], "8.1 2.9 34.6": ["fritti"], "6.0 4.9 41.9": ["picatta"], "9.4 7.3 2.8": ["empting"], "19.5 13.7 26.5": ["mayflower"], "8.9 17.1 9.6": ["bahubalis"], "-4.0 12.3 -3.0": ["pharmacotherapeutic"], "3.0 8.9 16.1": ["tnt"], "3.8 16.6 8.9": ["orgasmed"], "-2.6 13.1 1.8": ["chowkie"], "7.3 1.9 10.6": ["cafetaria"], "14.0 7.2 23.2": ["panipuri"], "4.8 23.4 5.9": ["disrespectable"], "20.4 13.8 13.3": ["sooths"], "-3.5 4.7 6.7": ["mazars"], "7.5 17.5 28.7": ["sinkin"], "7.5 15.3 10.0": ["shamal"], "-0.5 -3.0 4.7": ["demonstrational"], "19.4 7.1 18.9": ["photogenically"], "0.5 22.6 15.7": ["tautologically"], "3.1 21.2 16.8": ["legendaries"], "5.8 3.1 5.3": ["dxf"], "11.6 19.4 4.4": ["mibr"], "-5.6 16.0 -2.0": ["contary"], "2.8 7.1 2.2": ["atrioventricular"], "12.1 13.0 7.0": ["internalises"], "-4.2 -0.3 1.8": ["microcatheters"], "17.4 11.7 15.9": ["cristal"], "7.4 7.3 5.2": ["enrgy"], "1.3 0.5 7.0": ["extrabet"], "-2.6 9.7 4.4": ["themore"], "9.9 -4.8 12.7": ["cherokee"], "2.8 13.7 8.7": ["schizotypal"], "10.5 22.0 10.2": ["grubbering"], "7.6 3.5 12.8": ["resortwear"], "7.6 2.6 8.7": ["encontrar"], "13.2 17.2 24.7": ["jaeger"], "-2.2 24.6 13.5": ["gutcheck"], "-1.1 10.3 7.0": ["forus"], "-0.6 7.7 16.9": ["tono"], "13.3 2.0 3.1": ["binnen"], "6.6 9.2 14.0": ["ontogenetic"], "-14.4 10.7 3.4": ["rabbanim"], "6.3 27.5 11.4": ["tyrannise"], "4.7 22.0 11.9": ["antiproliferation"], "20.4 5.9 14.8": ["unclamp"], "4.1 6.5 9.7": ["incidentalomas"], "9.0 15.8 9.1": ["ceratin"], "-0.6 12.8 2.9": ["accelerometry"], "6.8 5.8 7.8": ["fsf"], "5.6 -7.8 2.8": ["ottobre"], "0.0 2.3 -1.8": ["nonmortgage"], "-1.9 10.3 4.5": ["heterozygote"], "2.2 18.5 4.9": ["shouldhave"], "2.9 8.5 9.9": ["diathesis"], "6.7 -0.3 9.9": ["reimplementing"], "0.2 -1.5 2.6": ["reivew"], "6.5 4.6 17.5": ["bifidobacterium"], "6.9 4.5 25.8": ["cua"], "17.1 16.0 6.1": ["halleluiah"], "2.8 18.7 17.0": ["pentamer"], "11.9 15.8 23.5": ["firepot"], "9.7 10.0 13.4": ["microwires"], "13.2 6.2 7.4": ["noncable"], "13.3 15.8 14.7": ["scansion"], "6.4 -2.6 22.0": ["strathspeys"], "2.2 -2.1 21.4": ["gilders"], "13.9 8.5 -1.3": ["ngiht"], "7.5 4.4 2.7": ["fornix"], "-5.0 -0.2 1.9": ["convenership"], "9.1 4.4 9.8": ["indic"], "2.5 8.6 15.0": ["conrad"], "-2.5 13.8 7.6": ["deicision"], "-0.3 13.0 8.6": ["mathmatics"], "3.7 -0.2 -0.7": ["esearchers"], "5.9 5.9 6.5": ["honneur"], "2.8 16.6 17.7": ["jangan"], "-5.3 1.5 -2.9": ["invesitgation"], "1.1 10.9 -3.1": ["relinguish"], "7.8 14.8 -4.0": ["discreetness"], "3.5 2.0 8.8": ["undercollected"], "11.7 16.1 3.7": ["spectated"], "-4.0 11.6 14.0": ["nowcasting"], "5.7 13.9 8.8": ["ogun"], "4.6 2.2 11.0": ["meilleure"], "15.9 13.0 16.1": ["unthreaded"], "0.8 24.5 3.3": ["wanainchi"], "12.2 16.1 12.9": ["radarscope"], "13.1 -0.9 12.5": ["maxidress"], "0.9 11.6 16.4": ["suna"], "-0.8 8.1 8.8": ["postals"], "11.2 10.0 5.2": ["overcommercialization"], "0.9 4.8 0.5": ["muchmore"], "6.9 4.3 5.9": ["vew"], "-6.2 9.1 0.9": ["girlchild"], "-3.4 18.2 0.1": ["aggree"], "-8.2 22.4 2.0": ["confessionally"], "7.5 15.1 6.5": ["twistiest"], "-7.4 2.5 5.0": ["britt"], "12.9 18.4 17.9": ["yoda"], "8.0 -8.7 4.8": ["chich"], "11.7 6.1 12.5": ["basse"], "-3.2 12.9 5.2": ["ponderable"], "10.2 -0.7 4.3": ["oglemilast"], "13.0 11.7 14.7": ["gooooood"], "12.1 17.3 3.2": ["exorcizing"], "10.1 3.3 10.1": ["parvis"], "11.8 3.8 12.7": ["brewmeister"], "6.0 6.3 5.2": ["restomod"], "14.0 11.0 25.2": ["rosogolla"], "13.4 5.9 14.6": ["pones"], "7.2 2.1 -0.8": ["peugeot"], "18.9 31.7 -0.5": ["defeater"], "2.8 2.3 3.0": ["hounour"], "4.4 12.0 30.5": ["pye"], "2.0 1.9 4.0": ["archabbey"], "0.0 7.4 13.4": ["clavo"], "11.3 7.7 12.3": ["separte"], "-3.7 3.7 -3.0": ["indited"], "17.1 10.7 40.2": ["zushi"], "27.4 4.8 0.6": ["companes"], "13.6 8.9 21.6": ["heinies"], "-2.3 2.8 15.2": ["gfs"], "0.6 19.3 8.6": ["mutans"], "8.5 3.6 21.2": ["steersperson"], "-6.7 17.8 5.2": ["contempts"], "1.8 4.1 37.3": ["partyboat"], "7.5 22.8 21.8": ["leafminer"], "13.5 21.8 20.0": ["fumbly"], "3.2 5.1 9.4": ["celebate"], "11.5 2.5 20.3": ["monokinis"], "3.5 1.9 10.6": ["ergos"], "-1.1 4.9 9.6": ["refracture"], "8.8 7.4 17.8": ["owly"], "2.1 8.8 20.7": ["fruitiest"], "7.5 4.6 12.7": ["jabots"], "-7.1 8.6 18.0": ["kwarta"], "5.8 9.3 3.1": ["recategorised"], "4.5 15.1 -1.2": ["unconcentrated"], "8.2 20.7 6.7": ["wheatgrowers"], "6.1 12.0 3.2": ["authourity"], "6.3 9.6 13.1": ["weedicide"], "17.5 5.7 13.3": ["falla"], "19.0 -6.7 13.3": ["custommade"], "7.0 3.5 7.3": ["redrilling"], "6.1 4.8 4.8": ["hosital"], "4.9 10.4 16.3": ["yorkies"], "9.7 17.1 16.3": ["flavenoids"], "-0.0 7.1 12.0": ["irl"], "14.6 7.6 34.9": ["shawerma"], "-0.9 13.7 7.4": ["couchsurfers"], "10.0 14.7 1.6": ["creasingly"], "11.9 9.6 7.2": ["androgenous"], "-5.7 4.9 2.9": ["copolyesters"], "4.8 25.0 7.4": ["enthrones"], "6.1 13.8 8.9": ["wissen"], "28.7 21.0 24.1": ["oilcan"], "10.2 3.5 14.3": ["feaures"], "-3.1 -1.4 -0.4": ["betweent"], "4.7 3.4 -1.0": ["fffoo"], "-2.6 8.4 2.2": ["preseaon"], "1.8 -2.6 8.7": ["hcg"], "2.3 -1.7 20.2": ["teria"], "16.5 9.4 8.5": ["entier"], "-3.4 5.2 1.8": ["agences"], "26.1 10.6 14.4": ["whoof"], "5.8 10.7 20.5": ["victual"], "1.3 3.6 1.5": ["enouraged"], "5.5 10.3 9.8": ["minislump"], "17.2 9.5 14.6": ["malled"], "8.0 -2.5 4.1": ["magasin"], "5.4 10.4 15.8": ["ophthalmia"], "14.9 9.4 21.9": ["haberdasheries"], "-3.3 7.7 16.5": ["lahi"], "2.3 15.5 7.8": ["punishement"], "7.1 6.8 22.2": ["intermedius"], "4.4 0.8 14.7": ["tze"], "3.4 4.9 12.2": ["hahs"], "-0.6 5.7 2.0": ["shetty"], "6.4 6.1 7.1": ["increasers"], "5.9 40.8 13.0": ["spellcasters"], "12.3 16.2 5.1": ["unbeliveable"], "-0.6 12.9 6.8": ["incohesive"], "7.4 10.0 11.2": ["mediumpacer"], "0.2 8.4 6.4": ["inductances"], "-14.6 -3.7 10.9": ["urethroplasty"], "8.7 7.2 3.4": ["optimisers"], "1.6 8.3 5.4": ["subdiscipline"], "7.8 6.6 12.0": ["incresing"], "0.7 7.3 16.6": ["ndy"], "15.1 0.4 3.3": ["fruad"], "-6.0 16.0 12.4": ["imprtant"], "-1.4 10.6 30.3": ["halophyte"], "4.9 11.2 14.6": ["volutpat"], "5.4 11.2 5.1": ["woulld"], "17.3 29.7 19.7": ["merfolk"], "6.8 4.3 5.0": ["milliamperes"], "3.6 8.2 9.0": ["gvern"], "9.0 8.0 27.5": ["burra"], "14.7 8.2 18.1": ["ungallantly"], "16.2 9.7 3.8": ["procurment"], "-4.2 0.1 17.5": ["parrish"], "18.5 2.0 8.2": ["mitsubishi"], "16.3 3.4 2.2": ["thefirm"], "16.7 11.9 8.1": ["cartwheeler"], "15.1 4.1 16.5": ["huffers"], "4.5 11.0 18.4": ["cypin"], "18.1 10.4 24.4": ["fuzzballs"], "-3.8 10.1 12.5": ["opisyal"], "15.9 6.2 6.3": ["sunsoaked"], "1.9 11.6 -4.6": ["computability"], "8.1 8.3 10.6": ["steepeners"], "10.5 12.7 11.9": ["tweening"], "15.2 0.8 3.3": ["photofinisher"], "9.5 7.0 4.5": ["polyisocyanurate"], "5.3 11.7 10.4": ["mutu"], "-3.6 6.4 10.2": ["flavanones"], "16.9 12.5 9.4": ["evolvable"], "7.6 14.5 5.8": ["soixante"], "15.3 1.8 12.1": ["retial"], "9.2 8.7 4.4": ["hyperarticulate"], "-1.0 14.1 9.7": ["uncommitteds"], "7.4 8.0 20.8": ["capitata"], "3.9 17.5 13.4": ["schlockfest"], "4.8 9.0 8.5": ["regroupings"], "4.4 -4.2 5.2": ["leukoderma"], "2.2 18.6 6.7": ["signle"], "9.8 6.7 30.0": ["sando"], "6.6 3.0 9.9": ["affg"], "4.7 0.7 11.9": ["ilmenites"], "-4.8 0.8 2.2": ["sihn"], "-2.2 -8.7 1.4": ["ampacity"], "17.0 15.0 26.8": ["blanding"], "2.7 14.2 9.2": ["understatment"], "0.4 4.2 13.5": ["spina"], "15.5 18.7 15.1": ["humpers"], "10.3 14.0 11.5": ["clownery"], "0.6 8.5 11.7": ["oversing"], "11.9 17.0 9.2": ["thiis"], "6.7 -1.4 5.0": ["togenerate"], "-0.9 8.5 9.4": ["thiourea"], "1.9 16.2 0.8": ["workpaper"], "20.8 -4.3 7.2": ["thumbtacked"], "0.9 1.5 12.6": ["sawan"], "-9.0 -7.1 -3.8": ["peripartum"], "-1.4 8.1 17.3": ["opo"], "3.0 -2.6 2.0": ["sds"], "21.7 26.7 8.0": ["catastophe"], "-2.0 -1.6 9.6": ["musicforthemorningafter"], "1.9 10.8 13.2": ["mannerable"], "5.4 9.0 3.4": ["penlights"], "6.2 12.5 3.6": ["overclaim"], "4.2 2.6 16.1": ["ewan"], "5.4 8.6 0.2": ["treshold"], "14.6 4.5 6.8": ["powerpacked"], "21.5 1.5 15.8": ["brontosaurs"], "14.6 7.2 11.8": ["nanograss"], "19.1 18.5 13.8": ["accommodatingly"], "-1.5 -2.5 5.2": ["ando"], "6.7 8.0 24.7": ["galanga"], "18.0 13.6 34.8": ["cherimoyas"], "3.3 10.9 1.4": ["produceable"], "7.8 18.0 27.6": ["precocial"], "1.3 17.5 9.0": ["embrassing"], "-1.7 13.9 14.9": ["yahi"], "12.8 13.2 12.3": ["muzungu"], "-1.7 9.2 21.6": ["khun"], "3.2 13.6 7.5": ["worbo"], "3.4 -0.5 3.7": ["impleadment"], "9.8 17.6 2.9": ["multijunction"], "10.8 10.3 15.4": ["eskers"], "-4.5 9.5 6.9": ["lexically"], "5.9 7.2 15.8": ["nitrox"], "3.9 7.7 8.5": ["nonagency"], "12.2 8.0 12.9": ["fcuking"], "11.0 4.0 4.2": ["municiple"], "10.8 1.3 15.5": ["sneakered"], "5.7 27.6 0.7": ["eternalize"], "16.1 0.1 1.5": ["unembossed"], "-4.8 11.3 6.6": ["lowerclassmen"], "-0.5 7.7 3.7": ["unequitable"], "4.7 5.9 2.6": ["doning"], "7.3 -2.2 3.2": ["inrease"], "15.4 9.9 17.8": ["shmoe"], "23.8 5.7 10.3": ["bigges"], "7.1 6.0 11.7": ["prefectly"], "8.3 0.6 6.5": ["enteroscopy"], "-3.2 19.2 7.7": ["actally"], "4.4 16.8 10.3": ["nebulousness"], "4.4 6.5 2.4": ["feder"], "17.4 24.8 9.2": ["weaponeers"], "11.7 17.2 6.3": ["notspots"], "4.4 -3.3 3.3": ["linefill"], "10.1 13.0 6.5": ["nomex"], "-8.6 2.0 -6.3": ["thatin"], "16.6 4.7 9.5": ["unruled"], "5.4 9.3 2.4": ["husting"], "4.2 18.9 -4.4": ["forumers"], "15.5 5.3 12.2": ["trucky"], "-2.1 5.6 5.9": ["regan"], "-4.6 17.7 1.0": ["offduty"], "2.0 16.1 15.7": ["juvies"], "2.7 3.6 15.4": ["rire"], "-2.6 12.5 8.4": ["splitboard"], "14.1 6.4 24.7": ["megas"], "6.7 14.4 19.1": ["scrappin"], "6.7 -0.8 11.5": ["timespread"], "3.0 11.5 5.8": ["hapiness"], "22.5 -6.1 6.8": ["skatewear"], "5.3 -2.9 3.6": ["travelgate"], "20.6 8.7 13.2": ["colouful"], "2.2 4.1 9.9": ["jurys"], "10.4 9.6 7.5": ["waymarking"], "2.7 8.0 19.3": ["hyaline"], "8.9 -0.8 13.1": ["onestop"], "5.0 -1.8 5.0": ["pudo"], "22.4 13.3 13.3": ["incrusted"], "8.4 -3.7 -0.2": ["uary"], "1.8 10.6 10.1": ["eben"], "10.8 7.1 2.8": ["thehospital"], "3.7 9.3 13.8": ["smithsonite"], "-6.1 4.6 10.5": ["repigmentation"], "4.7 -0.9 6.0": ["termina"], "-4.0 10.2 5.1": ["angrezi"], "9.0 1.0 12.7": ["sabar"], "1.5 -5.9 2.5": ["celebr"], "6.8 5.3 9.7": ["wolfe"], "14.2 25.1 3.4": ["bfbarbie"], "11.3 12.3 13.4": ["fluoresced"], "-5.9 9.4 -6.1": ["miniute"], "-0.5 3.4 -4.3": ["lawuit"], "5.9 8.7 11.9": ["schistose"], "11.2 17.9 19.7": ["blastoffs"], "2.9 12.0 5.9": ["alterity"], "10.7 0.6 -1.6": ["esreboxetine"], "7.3 10.6 15.6": ["teenspeak"], "6.9 1.7 16.1": ["frolf"], "-0.9 11.8 14.1": ["gago"], "9.0 9.4 -1.1": ["compatibilty"], "25.7 9.7 17.9": ["scraggily"], "2.1 -0.5 -0.7": ["tradi"], "-2.8 1.6 2.1": ["scs"], "2.0 8.5 4.2": ["instructionals"], "3.9 4.2 11.3": ["kafeel"], "-1.7 5.0 -6.2": ["jurisdication"], "3.6 4.4 9.9": ["underdosed"], "14.1 16.0 33.5": ["blacktails"], "7.7 10.9 14.1": ["aquatically"], "10.8 3.7 6.7": ["octanes"], "8.5 13.6 7.4": ["reconsolidating"], "13.3 -0.5 28.0": ["ristras"], "12.7 3.2 7.6": ["fertliser"], "7.6 28.2 11.9": ["victum"], "7.7 17.3 13.8": ["womanize"], "3.6 9.9 9.2": ["markerless"], "6.4 29.2 4.9": ["archons"], "15.1 10.6 19.5": ["prehispanic"], "13.9 8.7 16.8": ["compiz"], "9.8 10.8 11.6": ["unstow"], "21.8 17.3 25.2": ["topmast"], "20.8 9.6 30.1": ["juliennes"], "3.4 18.8 1.0": ["justifed"], "7.3 1.8 12.9": ["orris"], "0.2 16.7 12.4": ["idealisms"], "6.7 12.4 22.9": ["octoroon"], "23.5 23.4 8.5": ["rottenest"], "-0.3 1.7 1.4": ["inelligible"], "3.1 7.4 11.3": ["largement"], "4.9 9.9 4.7": ["mbit"], "29.4 31.7 25.0": ["symbiotes"], "7.9 6.4 14.7": ["sini"], "15.1 4.4 -1.0": ["metalised"], "4.4 10.1 15.9": ["coonass"], "2.5 11.8 13.2": ["aufed"], "2.0 -3.3 2.0": ["msrp"], "-1.1 15.0 -2.4": ["abridgments"], "7.4 8.3 13.7": ["telefantasya"], "1.3 1.1 12.0": ["schultz"], "6.4 9.6 15.4": ["sooties"], "16.6 3.9 9.8": ["powerwash"], "11.2 7.1 4.5": ["arithmatic"], "-0.9 5.8 1.7": ["leadi"], "-5.6 -1.8 12.8": ["revi"], "-2.1 3.1 11.5": ["paga"], "4.1 4.8 5.4": ["depolarizing"], "17.2 2.8 19.7": ["busman"], "7.7 0.2 7.8": ["albiglutide"], "10.6 3.3 8.6": ["bioinstrumentation"], "8.1 14.9 11.2": ["puroresu"], "11.3 3.8 19.1": ["stah"], "0.5 0.4 -6.9": ["discusssed"], "3.7 0.8 2.3": ["closly"], "6.8 17.9 7.5": ["stagebound"], "-4.4 2.8 9.5": ["kopa"], "8.4 9.6 18.6": ["frugalness"], "13.4 17.6 10.8": ["vdv"], "-3.3 10.1 6.5": ["persent"], "-0.8 11.7 7.4": ["carla"], "3.1 20.8 8.4": ["characterological"], "7.3 15.8 11.4": ["godsakes"], "-1.5 8.1 4.0": ["linkbacks"], "9.0 24.7 5.3": ["uncomplicatedly"], "15.9 2.4 12.9": ["stoc"], "-5.3 7.6 -2.6": ["auditees"], "14.5 13.8 11.5": ["artes"], "-0.7 7.2 7.0": ["liekly"], "25.5 8.3 0.4": ["cashcow"], "11.8 6.2 7.3": ["ambiente"], "9.8 6.8 20.0": ["culchie"], "1.7 2.2 11.8": ["puwesto"], "25.7 11.9 23.3": ["knifefish"], "0.1 1.8 1.2": ["answersheet"], "20.8 15.2 29.7": ["tegu"], "-5.7 3.3 -2.5": ["sixstepsrecords"], "-1.4 9.2 15.2": ["bodoh"], "17.9 5.5 21.8": ["robbins"], "13.5 -7.8 10.3": ["multivenue"], "2.5 22.6 9.4": ["govenments"], "16.1 8.2 32.7": ["spearguns"], "5.7 -1.4 2.5": ["entrevista"], "4.2 -1.1 6.0": ["unaminously"], "9.7 2.0 7.6": ["shubh"], "10.8 8.4 9.9": ["rorty"], "10.5 7.8 29.1": ["polvoron"], "3.1 17.0 16.7": ["kcotham"], "5.8 25.7 4.0": ["politization"], "8.7 7.7 19.3": ["presettlement"], "4.8 22.4 4.5": ["unambivalent"], "-5.8 13.2 9.7": ["shadchan"], "3.5 4.8 15.8": ["microdermabrasions"], "5.5 14.7 10.8": ["douchiness"], "6.0 0.4 6.6": ["triethanolamine"], "8.3 17.2 15.3": ["clonked"], "-6.2 2.7 -3.4": ["adamcaplan"], "-3.0 7.6 1.8": ["undergrounded"], "8.7 -4.6 5.4": ["whitebooks"], "0.5 1.2 13.6": ["millimoles"], "8.2 19.0 19.2": ["wooh"], "3.5 9.4 7.3": ["imagen"], "-6.3 9.2 4.5": ["recommendees"], "1.0 -1.4 8.1": ["perdido"], "3.0 11.2 -1.5": ["calss"], "7.7 -11.2 0.7": ["sportshall"], "13.7 11.5 16.6": ["wristily"], "4.5 5.8 9.2": ["warri"], "14.5 18.4 7.8": ["antiviruses"], "11.2 5.9 19.0": ["sams"], "8.3 9.9 9.1": ["uruguay"], "9.7 17.0 26.8": ["ostracodes"], "-3.9 -0.6 3.9": ["ctp"], "10.0 5.6 11.7": ["instuments"], "7.4 6.9 20.0": ["mahihirap"], "7.6 17.5 11.3": ["thaty"], "-0.7 8.0 -0.9": ["documentarists"], "2.2 26.6 15.0": ["tradeskills"], "8.7 4.9 14.2": ["metaller"], "6.0 3.1 10.9": ["ibi"], "1.3 9.4 7.2": ["reburn"], "2.9 17.2 5.6": ["showes"], "8.9 3.2 7.0": ["microfiches"], "3.8 8.6 11.9": ["diferente"], "10.2 -5.8 -5.5": ["guaranted"], "-1.5 18.3 5.0": ["martyrology"], "3.2 8.1 23.0": ["riyan"], "11.7 9.1 24.4": ["grevillea"], "-8.3 6.2 8.4": ["endocervical"], "11.0 12.6 9.6": ["unclasp"], "0.3 2.8 -2.5": ["yourmoney"], "10.0 20.9 9.9": ["hisown"], "12.2 0.9 9.9": ["marade"], "13.5 -1.5 -6.6": ["featuers"], "7.3 8.7 9.4": ["lecteur"], "-0.4 0.4 1.9": ["railpass"], "0.3 6.5 18.4": ["benzoates"], "2.1 16.6 22.3": ["chitting"], "4.0 6.8 14.9": ["gymgoers"], "7.6 6.5 0.2": ["fanzones"], "10.0 3.8 11.8": ["cliente"], "6.5 22.8 7.0": ["fck"], "-0.9 -2.7 1.6": ["stitute"], "5.5 8.7 6.8": ["elex"], "4.5 13.6 12.1": ["battier"], "-2.6 8.8 4.8": ["complaintants"], "4.2 4.3 3.1": ["thad"], "-1.8 5.8 0.7": ["individiual"], "14.1 15.8 19.6": ["crooking"], "10.0 13.5 12.6": ["fritted"], "9.8 3.4 15.2": ["microtubes"], "6.1 9.3 14.9": ["hydrometeorologist"], "13.7 14.1 17.1": ["driblets"], "-5.4 11.9 7.6": ["attunements"], "13.2 9.0 18.2": ["boldfacers"], "17.2 16.4 20.0": ["rockfill"], "1.9 10.6 -0.8": ["favourities"], "2.0 10.4 0.8": ["sabhapati"], "7.8 -1.3 8.0": ["focued"], "0.5 18.9 8.0": ["evangelistically"], "8.5 8.7 11.2": ["prodigous"], "7.3 2.0 33.8": ["salinas"], "8.0 8.7 7.9": ["xpected"], "17.6 19.1 19.0": ["shriekers"], "4.3 8.7 14.6": ["deepak"], "8.0 1.7 2.1": ["rentailers"], "-2.8 9.6 3.4": ["aqnd"], "4.9 10.7 14.0": ["multichannelling"], "13.3 25.4 7.5": ["rabidity"], "10.6 0.2 15.9": ["chuang"], "8.7 7.7 8.3": ["supercurrent"], "10.2 4.9 13.6": ["actuelle"], "19.6 8.0 35.1": ["chickeny"], "7.0 8.7 8.3": ["sedimentological"], "18.2 2.2 7.5": ["bying"], "-4.5 6.8 5.6": ["jcrisp"], "0.4 7.8 8.9": ["glucosides"], "15.4 22.7 14.7": ["biohackers"], "0.6 11.1 10.5": ["suno"], "11.8 27.6 3.5": ["unflyable"], "14.7 13.6 9.6": ["metonym"], "2.5 5.7 17.9": ["iodization"], "2.8 6.6 8.2": ["hio"], "-1.6 8.9 3.3": ["illuminatingly"], "30.3 11.0 16.6": ["mahoosive"], "2.1 6.4 13.0": ["showshoeing"], "-5.3 1.7 -4.1": ["presdent"], "6.9 19.6 17.8": ["ashort"], "6.5 2.4 7.9": ["hexene"], "5.8 -1.5 13.3": ["maillots"], "-6.1 6.1 -1.4": ["adecision"], "1.3 0.1 12.8": ["rebonds"], "3.2 12.3 13.5": ["greenbug"], "7.5 4.6 3.9": ["gacked"], "-6.8 4.2 -10.8": ["wrotes"], "5.0 5.3 1.9": ["outster"], "0.9 13.4 10.0": ["uneditable"], "15.3 10.7 10.2": ["telerobotic"], "5.7 27.7 1.9": ["divisionist"], "1.0 6.7 8.4": ["vandana"], "18.2 16.0 8.3": ["plotholes"], "26.0 3.0 5.8": ["milllions"], "1.0 5.4 1.3": ["zanolimumab"], "-0.3 27.0 2.4": ["justificatory"], "1.6 22.0 4.6": ["mindbody"], "5.5 12.4 25.5": ["tarplant"], "-6.6 1.7 17.5": ["daba"], "18.5 6.9 8.4": ["deployme"], "3.9 6.7 8.7": ["extranjeros"], "15.0 13.3 7.1": ["streetlife"], "0.4 15.7 6.8": ["reedit"], "-6.3 2.9 -1.2": ["dyslipidemias"], "12.2 6.9 15.4": ["completamente"], "5.5 38.8 1.7": ["resistants"], "18.2 -1.0 9.0": ["indexrose"], "7.1 0.7 8.0": ["titanomagnetite"], "7.5 23.6 5.4": ["timestream"], "-3.9 10.3 -1.1": ["responde"], "5.6 2.4 3.7": ["bleiben"], "-11.5 -9.0 0.9": ["subrecipient"], "7.2 19.3 5.7": ["wiretappers"], "6.0 17.0 10.7": ["fireplugs"], "0.9 9.9 6.2": ["hyphema"], "7.6 12.1 9.2": ["treeview"], "8.1 1.3 15.5": ["luces"], "9.2 8.0 11.7": ["pandeiro"], "12.4 13.9 18.4": ["zestily"], "1.3 6.4 4.5": ["zr"], "6.8 16.5 23.2": ["outdoorswomen"], "12.6 14.4 15.7": ["busby"], "15.7 8.1 13.7": ["hubble"], "6.9 2.7 7.3": ["hydrotreaters"], "-1.2 14.8 -0.1": ["nere"], "3.3 8.9 5.1": ["yagam"], "12.0 4.1 14.2": ["louboutin"], "0.6 13.8 17.5": ["seakeeping"], "13.4 11.5 9.3": ["misaligning"], "11.8 -7.2 -3.3": ["prelet"], "-9.0 4.1 -0.0": ["retrievability"], "5.0 2.6 5.1": ["peptidome"], "8.8 18.8 22.6": ["deid"], "3.3 4.3 14.0": ["eab"], "13.5 21.4 17.9": ["whoomp"], "2.5 2.2 -4.3": ["agreedto"], "5.2 6.3 20.7": ["shortboarders"], "7.8 11.4 10.3": ["cambiar"], "6.1 -1.3 6.4": ["strauss"], "1.1 27.3 7.4": ["hotswap"], "9.0 -1.5 2.8": ["thouand"], "-5.4 7.3 15.5": ["passaged"], "4.9 2.6 25.9": ["shima"], "13.3 -1.1 14.0": ["bibelots"], "9.4 14.8 13.8": ["galloway"], "5.3 10.7 23.1": ["oolongs"], "12.5 8.2 17.2": ["shemales"], "15.5 4.2 -1.9": ["videocalling"], "-3.6 9.7 25.5": ["nonconsumptive"], "13.0 30.8 6.7": ["trickeries"], "-0.7 14.2 5.3": ["outspeed"], "2.6 11.1 36.1": ["giggers"], "11.5 21.2 11.1": ["gustnado"], "7.4 5.2 13.7": ["nawabi"], "9.5 1.6 14.2": ["chika"], "8.4 18.6 20.7": ["squa"], "5.9 8.9 9.2": ["divalent"], "8.5 17.4 17.7": ["misfielding"], "4.3 7.7 15.8": ["gompa"], "1.9 9.0 4.8": ["socring"], "11.1 6.0 4.0": ["synergises"], "3.8 19.0 8.8": ["culturalists"], "9.3 -10.2 11.2": ["zhay"], "18.3 1.8 17.4": ["trunkloads"], "12.1 21.5 10.1": ["gooderism"], "-5.3 14.8 13.8": ["unles"], "9.3 6.5 8.5": ["candidato"], "-7.1 -8.7 6.9": ["nulliparous"], "3.9 14.3 11.4": ["subkey"], "6.3 8.1 6.7": ["stereochemical"], "9.0 7.2 7.7": ["segun"], "4.9 12.2 19.3": ["ploidy"], "-0.4 3.0 11.9": ["lalabas"], "1.9 10.4 7.8": ["excpet"], "17.0 9.0 13.0": ["spanx"], "16.1 10.5 11.4": ["valorising"], "-3.4 9.1 1.8": ["theb"], "8.9 -4.1 30.1": ["pyrohy"], "3.4 12.9 5.2": ["consociational"], "-4.9 21.6 5.1": ["counterviolence"], "11.0 4.2 7.3": ["colla"], "5.6 7.3 3.0": ["parganas"], "4.6 26.0 2.1": ["deviationists"], "10.5 5.1 0.8": ["humyo"], "3.6 21.3 5.5": ["futilities"], "5.6 16.0 22.4": ["convivia"], "11.7 2.0 0.6": ["controvesy"], "17.1 4.8 24.4": ["phormiums"], "16.8 13.4 13.8": ["geforce"], "13.8 1.3 5.7": ["doemstic"], "6.5 2.2 4.7": ["desaturase"], "9.2 8.0 -1.1": ["spoksperson"], "2.8 9.3 1.5": ["yesterrday"], "9.3 -0.5 6.0": ["dishin"], "4.9 -1.2 11.3": ["iht"], "-1.3 -0.1 5.2": ["enz"], "16.8 6.8 12.1": ["trouserless"], "7.3 -2.5 7.3": ["lpd"], "7.4 1.5 13.8": ["nonbuilding"], "7.7 12.1 13.7": ["automatized"], "17.8 16.8 10.1": ["drumfire"], "-0.4 5.2 1.1": ["halten"], "10.0 7.9 6.0": ["increaser"], "9.3 9.5 7.0": ["partygoing"], "3.6 33.6 0.8": ["figthing"], "7.4 5.9 14.3": ["tfn"], "14.2 9.8 15.7": ["headspin"], "7.1 5.7 19.4": ["zha"], "10.6 9.6 17.3": ["foh"], "10.2 24.7 1.6": ["condemners"], "15.7 21.3 7.5": ["neutralinos"], "1.5 6.6 6.1": ["rememberances"], "8.1 20.0 8.4": ["fking"], "3.3 18.4 10.2": ["cogitative"], "9.7 17.8 14.9": ["resourceless"], "-4.0 2.6 -1.7": ["mansfield"], "1.4 6.3 9.9": ["ouverte"], "7.7 3.8 11.0": ["weree"], "2.6 7.7 4.5": ["mazdoors"], "4.7 12.4 11.4": ["myanmar"], "1.2 0.9 6.2": ["theremaining"], "1.8 14.4 4.9": ["temprature"], "2.5 12.7 17.6": ["babul"], "-8.2 -2.3 -1.9": ["etomidate"], "7.1 14.4 14.6": ["circs"], "12.0 9.4 7.9": ["dogpiling"], "12.9 12.1 7.8": ["micromarketing"], "1.2 8.9 12.1": ["goodman"], "2.4 -4.7 4.8": ["camilla"], "13.9 11.0 20.3": ["maaaan"], "4.7 23.0 8.8": ["bupkes"], "12.8 9.7 7.7": ["campuslike"], "5.7 7.9 6.5": ["nonoverlapping"], "2.3 22.0 4.1": ["oathing"], "-2.5 -3.6 8.3": ["samantalang"], "16.3 -1.8 -0.8": ["fuled"], "7.8 4.5 7.0": ["cantaor"], "15.6 16.3 24.5": ["crewless"], "11.9 -1.5 8.9": ["shoppping"], "5.3 11.1 8.1": ["kardashian"], "7.8 12.9 9.8": ["petless"], "15.2 15.5 15.2": ["assholery"], "10.3 12.2 12.6": ["bayah"], "-1.8 7.0 5.7": ["pasand"], "3.7 12.3 10.2": ["priesthoods"], "20.0 11.3 14.1": ["desperates"], "5.7 0.9 1.4": ["singl"], "9.1 3.5 -0.1": ["cfactor"], "11.2 15.7 27.2": ["boondoggling"], "13.7 4.3 34.0": ["kacang"], "2.8 10.8 11.3": ["kaibelf"], "11.1 10.4 5.3": ["newline"], "10.1 5.4 9.0": ["wnv"], "-0.2 15.8 15.3": ["moundsmen"], "8.1 6.3 7.3": ["github"], "9.4 10.0 3.3": ["ecent"], "10.6 10.5 13.8": ["abierta"], "13.7 14.6 21.1": ["bachi"], "4.4 11.3 15.1": ["presentability"], "10.4 1.7 7.0": ["multistore"], "8.2 6.1 11.0": ["strugglin"], "-4.0 3.9 -3.9": ["repondents"], "-1.1 3.4 18.2": ["munang"], "0.9 1.7 5.2": ["awqaf"], "10.7 8.9 12.0": ["glassworkers"], "1.2 11.3 15.3": ["humidifies"], "16.8 20.0 14.4": ["bunyip"], "-1.4 12.3 -3.9": ["commitement"], "16.2 18.7 9.9": ["whoopass"], "16.6 20.3 27.4": ["underwings"], "9.2 28.0 10.0": ["gangers"], "-2.6 -9.6 -2.7": ["esg"], "7.0 3.6 -2.7": ["dezineforce"], "0.4 -0.8 6.6": ["souza"], "15.6 3.6 9.3": ["pyromusical"], "4.0 7.0 12.9": ["stodgily"], "16.5 10.1 15.7": ["seoul"], "7.9 -7.1 2.4": ["codeveloper"], "-6.0 5.4 16.2": ["babalik"], "-3.6 9.8 2.9": ["awardable"], "-2.2 4.1 5.7": ["pher"], "2.3 -7.1 7.0": ["mrg"], "2.6 -0.0 16.7": ["wyth"], "-4.4 -2.8 3.5": ["rolli"], "7.2 7.9 14.7": ["ishing"], "-3.3 10.5 6.3": ["howthe"], "5.7 3.3 21.3": ["disinfestation"], "4.3 2.4 18.4": ["jhumkas"], "1.7 9.6 11.3": ["noncontributing"], "15.2 15.2 16.5": ["overexploiting"], "7.5 7.2 3.6": ["sprintf"], "3.2 -1.5 -7.3": ["policlinic"], "11.0 10.0 7.5": ["refugio"], "-5.3 11.5 9.2": ["pell"], "4.0 6.6 5.2": ["hoto"], "-4.9 1.2 9.4": ["auxilians"], "-1.8 9.3 -2.9": ["excruciation"], "0.9 6.7 11.3": ["pujo"], "4.1 -5.5 9.9": ["syncro"], "9.1 3.4 9.4": ["judith"], "10.0 8.0 13.6": ["soundscaping"], "28.9 5.1 9.2": ["megachain"], "10.6 2.2 12.8": ["estancias"], "11.9 3.3 4.5": ["torium"], "-2.9 1.9 1.5": ["togeth"], "14.4 11.1 7.0": ["lipouts"], "24.3 14.3 13.3": ["accesory"], "16.1 11.6 2.4": ["tized"], "4.0 7.4 11.7": ["shakkar"], "7.1 8.5 4.9": ["faite"], "0.8 19.8 -4.9": ["unscrutinised"], "3.2 18.5 3.4": ["misjustice"], "4.3 12.4 23.6": ["zincs"], "4.9 10.3 7.6": ["asem"], "4.4 -7.6 7.7": ["mercerized"], "6.4 6.6 9.6": ["roastings"], "6.5 5.7 13.5": ["leukapheresis"], "10.9 9.0 4.7": ["recesion"], "-12.2 2.6 2.6": ["ichard"], "9.0 18.4 11.5": ["humourlessness"], "1.0 -1.6 9.8": ["diacetylmorphine"], "-2.1 -4.7 4.2": ["facilitys"], "6.5 16.0 9.0": ["absoloutely"], "16.0 12.0 11.4": ["checkside"], "0.7 4.5 3.6": ["fictionist"], "0.3 -8.0 8.2": ["maitenance"], "6.2 8.9 11.0": ["jocose"], "-1.8 4.3 1.5": ["conten"], "5.0 -4.6 5.2": ["principaux"], "-4.5 10.3 14.8": ["cyclization"], "3.6 -1.4 9.8": ["amphiphiles"], "12.4 6.1 -1.8": ["pother"], "4.0 -0.4 8.1": ["mirex"], "8.7 19.5 14.2": ["germophobes"], "4.9 -0.0 13.2": ["fawr"], "-9.9 -4.6 -10.2": ["demit"], "14.9 19.6 19.2": ["pantleg"], "5.3 -4.5 11.4": ["luglio"], "3.7 11.1 3.7": ["rever"], "3.0 11.8 6.5": ["barablu"], "17.1 3.7 7.5": ["disgarded"], "7.6 4.2 13.6": ["tabor"], "-0.6 4.5 6.3": ["presswork"], "15.7 11.2 21.1": ["ovata"], "1.1 3.6 4.4": ["authour"], "22.1 7.8 21.3": ["cutty"], "20.1 19.4 18.1": ["presa"], "5.5 2.5 4.7": ["westbank"], "16.3 -3.3 14.5": ["soupmaker"], "5.3 9.9 19.5": ["arod"], "5.9 19.3 15.8": ["stochasticity"], "22.3 5.4 13.6": ["pedimented"], "9.1 9.9 14.7": ["sharpe"], "7.6 10.2 -0.7": ["criticisim"], "2.1 9.7 4.9": ["esimon"], "5.1 29.6 1.2": ["vicegerent"], "7.9 1.5 42.6": ["konbu"], "21.3 7.1 14.2": ["hightop"], "7.6 -2.8 7.3": ["livestrong"], "-0.2 -4.7 7.3": ["flighters"], "3.3 -3.2 18.3": ["worcester"], "9.9 3.5 12.6": ["doublewides"], "5.0 18.0 10.8": ["callisthenic"], "18.8 6.7 15.4": ["abarrel"], "1.6 2.4 1.9": ["policlinics"], "12.3 -2.9 8.7": ["superhospitals"], "0.1 12.4 15.0": ["polioviruses"], "8.9 -6.3 9.2": ["soluzioni"], "12.9 18.8 12.9": ["jackanapes"], "8.1 2.4 4.9": ["benchmarker"], "2.7 5.9 13.6": ["heung"], "11.5 7.5 15.3": ["uncaffeinated"], "5.3 3.4 4.5": ["capactiy"], "6.2 3.0 10.5": ["steppings"], "2.8 22.9 11.4": ["dispise"], "7.3 9.8 9.2": ["miswak"], "-0.4 -1.7 -4.0": ["exectuive"], "4.8 4.5 17.5": ["hackamore"], "10.2 5.1 31.3": ["turon"], "9.0 3.8 -1.0": ["kwachas"], "17.3 13.2 15.1": ["binkie"], "-1.3 11.1 2.7": ["hypometabolism"], "-3.5 2.6 -3.4": ["volumn"], "10.5 1.0 16.4": ["lunesta"], "23.4 -7.6 2.5": ["roadbuilder"], "-0.6 0.3 3.0": ["synaptogenesis"], "4.3 16.4 12.4": ["nonprotected"], "1.0 2.9 1.6": ["unagreed"], "20.1 11.3 16.7": ["tansu"], "7.8 -0.8 46.4": ["fileted"], "10.5 4.5 17.7": ["replating"], "0.7 13.8 -1.2": ["tthis"], "17.3 1.4 26.8": ["cloudberry"], "0.2 10.5 0.5": ["esseesse"], "6.7 6.0 8.5": ["realizar"], "9.2 9.4 11.0": ["fridaynightbash"], "17.7 6.0 34.1": ["somen"], "10.8 7.9 6.1": ["tinkhundla"], "5.6 6.5 10.0": ["epinastine"], "10.6 30.1 16.5": ["overcutting"], "11.9 18.9 8.8": ["hypermasculinity"], "3.2 18.7 6.4": ["filtrated"], "21.1 22.5 25.2": ["sasquatches"], "2.0 9.4 3.2": ["annal"], "11.7 20.3 15.5": ["dimwittedness"], "11.8 19.9 18.6": ["rincewind"], "0.4 9.3 16.3": ["intriga"], "4.5 18.0 19.3": ["gorehound"], "5.8 2.9 22.0": ["turbinado"], "3.7 5.0 11.9": ["banyak"], "-0.7 4.3 1.2": ["hemodiafiltration"], "4.1 23.9 3.0": ["churls"], "11.6 9.0 8.7": ["recarved"], "8.9 -0.6 12.6": ["impregnator"], "3.2 35.9 5.1": ["freedon"], "-0.8 0.4 -3.8": ["dualed"], "6.8 22.9 13.1": ["immitate"], "10.7 13.6 8.4": ["picure"], "9.6 6.5 6.4": ["sharin"], "7.9 -2.4 -0.4": ["ondon"], "1.7 10.3 10.2": ["isotypes"], "18.4 21.2 24.6": ["wolfy"], "5.0 17.0 9.1": ["sourse"], "12.8 9.6 13.3": ["sibilants"], "18.4 10.1 11.7": ["grouching"], "-7.1 6.2 -1.1": ["meaninful"], "19.4 7.3 5.3": ["qtly"], "6.9 26.2 9.2": ["chastens"], "2.8 9.6 -2.7": ["preconfigure"], "18.4 6.7 20.7": ["topazes"], "5.2 11.1 -0.1": ["transferences"], "4.6 9.9 18.4": ["digestions"], "16.4 11.2 11.3": ["gammas"], "2.9 11.1 8.0": ["gto"], "0.1 6.0 0.8": ["palatine"], "-0.1 7.9 7.1": ["supratentorial"], "6.5 8.5 3.6": ["bishopry"], "11.0 13.9 7.5": ["theworst"], "11.2 8.1 10.7": ["interdigital"], "9.0 8.7 14.3": ["lika"], "15.5 13.4 9.0": ["bx"], "4.9 7.1 14.0": ["harrington"], "11.8 5.2 6.1": ["furbish"], "14.0 4.0 12.1": ["wholesellers"], "1.9 8.6 9.9": ["osteoid"], "1.0 7.2 0.4": ["nonviral"], "0.4 14.1 2.2": ["imans"], "11.1 14.0 20.3": ["thoroughout"], "8.2 30.3 0.3": ["ultrasecret"], "13.2 14.8 6.6": ["itus"], "15.3 -0.4 10.6": ["smoothers"], "12.8 5.6 -1.8": ["preinstallation"], "12.7 12.9 29.4": ["goya"], "8.9 1.5 0.6": ["foundin"], "6.4 17.1 0.6": ["unloyal"], "8.5 -12.3 -1.1": ["announcedthe"], "7.6 11.3 9.0": ["trichloramine"], "4.4 12.3 7.2": ["pjackson"], "10.5 5.5 14.5": ["approachs"], "0.6 24.1 10.5": ["overtested"], "13.3 3.8 3.2": ["ednesday"], "13.9 13.1 11.5": ["gluon"], "15.6 19.3 15.7": ["monotoned"], "8.0 10.2 37.5": ["amatriciana"], "14.4 4.9 14.0": ["einstein"], "4.4 8.5 1.3": ["devlop"], "3.4 4.8 2.1": ["fasp"], "11.0 0.5 9.7": ["davalintide"], "7.6 -2.1 9.1": ["fiscale"], "23.6 -3.2 15.4": ["plam"], "3.9 3.6 12.4": ["hundis", "packman"], "6.0 8.3 5.2": ["toroids"], "8.7 16.5 16.4": ["desaturate"], "12.5 0.0 9.6": ["andmanufacturing"], "9.0 2.3 20.2": ["biofortified"], "4.4 5.9 11.6": ["planches"], "-4.6 6.6 8.9": ["outcurled"], "13.6 8.1 31.1": ["duckers"], "14.0 8.7 14.6": ["submicrometer"], "12.4 13.9 10.7": ["liketo"], "13.4 11.6 25.8": ["yins"], "8.5 24.4 16.3": ["devilishness"], "16.3 3.4 11.0": ["whitewall"], "1.2 -3.7 4.4": ["intital"], "9.5 5.1 11.9": ["nms"], "5.5 7.1 15.1": ["tomorro"], "9.2 12.3 -6.5": ["predessor"], "10.7 7.1 9.7": ["abouth"], "12.8 7.5 26.8": ["pipistrelles"], "6.0 2.8 7.8": ["delipidation"], "3.7 16.6 11.4": ["pasi"], "2.5 8.2 6.2": ["multipole"], "13.6 13.2 13.7": ["bogusness"], "-3.1 18.2 6.2": ["clonogenic"], "1.7 8.3 -3.8": ["installement"], "6.4 11.5 8.9": ["sideblades"], "4.4 3.6 12.8": ["chy"], "-2.6 6.6 -0.5": ["interbranch"], "-3.1 5.9 6.2": ["immunosuppressives"], "13.3 4.7 19.8": ["fruitgrowers"], "6.6 10.1 6.3": ["versitility"], "-1.8 9.0 12.1": ["preemergence"], "5.5 3.9 5.6": ["finalement"], "22.3 4.4 13.4": ["mallrat"], "5.1 13.2 4.6": ["gliosis"], "-5.7 4.4 6.5": ["bipolars"], "14.5 -6.3 -2.2": ["purchsed"], "7.9 17.2 17.8": ["knucks"], "-5.1 8.3 6.0": ["mincha"], "15.1 20.2 20.7": ["stoved"], "6.4 14.3 14.6": ["reation"], "1.7 11.0 -1.2": ["ajoint"], "0.0 -1.8 1.9": ["theoverall"], "10.4 5.7 13.0": ["cheshire"], "14.6 6.3 36.9": ["ayu"], "-0.7 -2.0 7.0": ["interfund"], "11.3 5.0 9.8": ["dax"], "4.3 18.3 12.6": ["loseable"], "9.7 9.0 7.6": ["pluckings"], "3.3 -1.6 7.7": ["kinetin"], "16.3 12.8 18.2": ["pomeranians"], "-3.4 13.1 2.4": ["menschy"], "2.5 -9.3 -1.1": ["vih"], "12.6 11.3 18.0": ["arcadian"], "8.3 15.1 15.1": ["pinschers"], "6.7 -3.9 16.4": ["pizzaria"], "-2.6 -2.4 6.3": ["nasogastric"], "11.6 -1.7 2.5": ["addreses"], "16.2 13.6 28.7": ["lavatera"], "2.3 14.8 10.1": ["sabko"], "-3.1 4.5 3.5": ["laxation"], "-3.5 9.4 3.2": ["atal"], "11.6 24.3 6.3": ["rethugs"], "-4.1 9.2 4.1": ["paragangliomas"], "5.3 2.3 17.2": ["heathly"], "9.9 11.0 5.6": ["solutionsthat"], "15.8 5.4 14.5": ["romanesque"], "13.4 11.9 7.7": ["technicans"], "2.9 -1.5 3.1": ["premio"], "-5.6 12.8 5.1": ["cytoreduction"], "7.0 15.3 12.3": ["mistermet"], "-1.7 9.7 3.1": ["notin"], "2.6 -5.1 6.9": ["weeeks"], "2.4 6.5 9.9": ["studliness"], "11.4 9.0 12.6": ["squre"], "-2.1 23.3 8.9": ["overexaggerate"], "17.1 3.3 32.1": ["sfogliatelle"], "8.3 6.9 12.5": ["gwon"], "8.4 18.4 5.9": ["neshamah"], "11.4 0.1 25.2": ["hulas"], "19.9 10.4 31.5": ["mariposa"], "1.9 20.1 19.7": ["abuelos"], "6.9 10.7 22.7": ["tasar"], "7.7 11.4 5.3": ["eady"], "9.1 0.2 7.4": ["siter"], "8.2 5.9 -2.3": ["irregularites"], "3.3 0.1 12.5": ["rhaglen"], "6.3 4.6 7.2": ["mapless"], "0.9 17.1 9.3": ["argumentativeness"], "7.5 9.8 8.2": ["makefile"], "14.5 7.5 2.5": ["electromedical"], "3.3 19.2 7.3": ["sophmoric"], "6.0 2.8 4.6": ["heterotopic"], "19.9 23.5 4.3": ["ominious"], "13.0 8.6 11.3": ["thousandaire"], "14.3 7.8 11.8": ["distends"], "13.2 -4.2 5.0": ["dics"], "5.2 -2.0 8.8": ["topbills"], "-8.7 11.7 4.9": ["boardsmanship"], "6.8 14.4 10.7": ["acters"], "15.5 15.5 6.6": ["allllll"], "6.0 4.1 8.5": ["tarea"], "5.3 2.0 12.9": ["asheville"], "5.0 5.3 14.6": ["dakshina"], "0.1 14.4 10.2": ["tazias"], "-1.9 6.7 4.1": ["atbat"], "-2.9 8.1 3.1": ["parahippocampal"], "26.0 7.7 14.4": ["drumrolls"], "7.6 4.7 20.5": ["cinchona"], "1.8 5.4 4.0": ["radioprotection"], "13.0 20.7 0.0": ["destablised"], "11.4 16.2 3.9": ["heavying"], "15.4 14.8 27.4": ["nutlets"], "4.4 -3.8 4.3": ["schvitzing"], "0.2 1.5 8.5": ["guhl"], "-3.6 0.3 1.5": ["shree"], "6.2 6.2 15.2": ["anicuts"], "5.2 -0.5 14.1": ["taf"], "-1.2 19.6 13.6": ["salmonellae"], "6.4 10.0 13.1": ["skywatcher"], "6.8 10.6 6.4": ["indigenized"], "8.3 8.2 15.8": ["punctate"], "12.1 8.1 6.1": ["pulser"], "2.0 -4.2 3.6": ["ballparked"], "4.2 12.6 14.2": ["tardive"], "15.1 6.5 7.1": ["pfffft"], "0.5 11.0 14.7": ["vallhund"], "4.6 11.5 19.8": ["higglers"], "5.2 16.3 7.2": ["worldism"], "-4.4 9.3 9.3": ["catechumenate"], "-15.4 -0.7 5.1": ["dians"], "6.5 -3.7 7.4": ["seesion"], "0.3 12.9 5.3": ["barazas"], "7.0 8.9 16.0": ["firangs"], "12.5 19.4 8.3": ["unimagineable"], "12.7 12.4 5.7": ["scences"], "14.9 16.3 15.8": ["freeter"], "3.5 -0.3 3.2": ["sorors"], "5.4 3.8 11.5": ["counc"], "-2.3 10.3 14.4": ["interracially"], "8.6 7.0 3.3": ["havemade"], "0.0 -1.2 14.4": ["findwell"], "-1.7 8.5 -1.9": ["estop"], "4.7 1.4 13.2": ["pyloric"], "0.1 13.8 2.5": ["acomplish"], "14.3 -4.3 36.0": ["malassadas"], "0.2 9.9 0.6": ["seriosuly"], "6.4 4.4 3.4": ["efficaciousness"], "13.3 11.8 10.5": ["leathermen"], "7.6 2.4 0.6": ["computerless"], "-5.5 8.3 1.2": ["xxxv"], "14.7 16.0 16.7": ["casper"], "12.3 7.8 18.7": ["nellie"], "12.1 10.1 6.5": ["coronating"], "22.2 13.2 2.4": ["behindthe"], "6.0 2.9 0.2": ["failedto"], "-3.2 -6.8 4.6": ["extramurally"], "9.8 28.1 10.0": ["illusioned"], "21.2 15.4 17.7": ["leggiest"], "0.9 15.4 14.8": ["soun"], "4.8 1.4 8.8": ["unico"], "1.5 8.2 -2.6": ["transposable"], "3.2 4.5 2.6": ["aleglitazar"], "7.2 12.3 12.0": ["unsynchronised"], "-0.2 -2.1 6.8": ["strikerate"], "18.2 8.0 33.8": ["galaktoboureko"], "-4.1 3.1 -0.1": ["rdc"], "10.9 3.7 26.9": ["ramyeon"], "-2.0 22.1 10.9": ["betweenness"], "10.9 19.7 4.6": ["prevelent"], "1.8 10.1 -5.1": ["telegrammed"], "12.6 11.4 26.6": ["tenderised"], "6.7 -1.0 2.2": ["predelivery"], "18.3 1.0 4.8": ["superloo"], "11.4 11.5 10.6": ["backlashed"], "24.4 2.4 17.7": ["scuplture"], "2.5 9.2 -3.9": ["overexposures"], "-1.4 19.3 0.4": ["crimminal"], "8.1 20.0 16.8": ["uncomely"], "3.1 21.5 14.7": ["companionate"], "4.2 13.0 8.4": ["resave"], "24.4 13.2 19.6": ["footwide"], "6.8 1.7 10.6": ["byd"], "-9.2 10.9 3.0": ["hudood"], "9.3 11.3 26.9": ["suiseki"], "1.8 15.9 13.8": ["jardine"], "23.3 9.9 16.5": ["roadheader"], "7.7 8.2 12.5": ["wainwright"], "9.7 -0.4 20.9": ["lotfeeders"], "1.0 -6.7 -0.3": ["generalmanager"], "18.1 6.4 10.7": ["flashpots"], "-2.6 23.0 12.5": ["overanalyse"], "16.7 4.0 -4.3": ["interative"], "6.6 12.3 9.9": ["saunders"], "8.0 11.9 47.5": ["goatfish"], "1.2 8.3 10.3": ["iona"], "1.2 4.6 8.9": ["wheezers"], "13.7 -2.3 18.0": ["shmoozed"], "24.7 16.4 26.5": ["ocotillos"], "12.2 1.5 5.5": ["yetserday"], "0.6 7.0 9.0": ["orpiment"], "0.3 15.2 1.2": ["candidiates"], "10.3 23.6 24.4": ["mosquitoe"], "-0.0 7.6 5.8": ["abadi"], "9.7 1.3 8.1": ["topsheet"], "17.3 -4.1 20.4": ["huggies"], "13.7 -4.6 10.2": ["velours"], "4.2 4.8 29.7": ["anchos"], "12.5 6.5 11.8": ["banane"], "7.7 11.6 20.2": ["agam"], "6.3 16.7 0.0": ["declassifications"], "1.3 -5.0 -3.2": ["undisc"], "8.7 7.0 13.7": ["floppier"], "-17.1 -24.8 -15.0": ["etwcf"], "0.5 9.2 3.4": ["localizers"], "9.9 10.6 28.7": ["lochan"], "13.5 0.8 2.5": ["dreamchild"], "10.6 18.2 19.5": ["downgrain"], "18.7 9.0 19.0": ["teethe"], "25.6 12.4 9.2": ["turnable"], "14.8 12.2 27.0": ["mossback"], "2.0 1.5 8.4": ["processus"], "1.9 -4.2 1.0": ["fernandes"], "7.6 14.0 13.1": ["sarcasms"], "-2.1 6.9 0.4": ["executively"], "22.1 19.1 2.6": ["coshes"], "16.1 13.0 23.9": ["intae"], "-4.3 5.5 12.2": ["ido"], "3.2 11.7 1.1": ["performativity"], "24.6 9.4 31.4": ["madrones"], "1.6 -7.2 7.9": ["cmo"], "7.5 12.9 38.8": ["spey"], "5.6 -3.0 7.5": ["subagency"], "6.3 6.1 6.0": ["rewatchable"], "4.9 4.7 13.3": ["jaaka"], "-2.7 16.4 17.4": ["outbreeding"], "1.7 -0.3 9.8": ["pma"], "0.2 14.7 6.0": ["generall"], "-3.9 4.1 7.2": ["alec"], "9.2 6.6 7.5": ["wenig"], "3.7 -3.6 20.2": ["bosco"], "5.7 5.3 2.1": ["incentivization"], "-2.2 11.4 10.2": ["cabalen"], "6.8 11.1 8.6": ["watford"], "1.8 1.9 1.7": ["mannan"], "-6.5 -1.5 -7.0": ["pka"], "16.6 3.8 15.7": ["hershey"], "9.8 8.4 21.9": ["muddin"], "7.8 3.9 6.5": ["morsing"], "4.1 11.7 2.3": ["suer"], "-6.1 3.5 -1.4": ["nadolol"], "12.8 3.8 9.2": ["angadia"], "5.0 15.1 12.7": ["zanaflex"], "0.4 17.8 6.7": ["saintlike"], "-4.4 -0.2 12.1": ["relocatables"], "7.2 18.2 14.6": ["ballcoach"], "13.7 -2.4 39.7": ["peperonata"], "6.0 7.0 13.9": ["droite"], "3.8 1.6 13.9": ["vinclozolin"], "14.8 3.1 14.2": ["sixtyish"], "0.5 -1.0 8.5": ["essai"], "4.4 6.5 -0.2": ["unchains"], "11.1 9.7 4.5": ["tocustomers"], "11.9 19.9 19.1": ["paramo"], "3.1 5.4 2.4": ["astay"], "5.3 18.7 11.7": ["relagation"], "6.5 11.0 5.5": ["antagomirs"], "1.2 6.3 14.4": ["wata"], "9.3 18.0 4.0": ["lobbiests"], "5.4 4.3 8.9": ["naniniwala"], "2.2 12.7 3.3": ["stregnth"], "5.9 20.4 12.8": ["vehilces"], "3.2 4.3 0.6": ["esignature"], "10.9 11.2 10.7": ["alleluias"], "2.8 2.7 5.0": ["currier"], "1.6 17.3 3.4": ["sania"], "-1.0 3.7 0.8": ["thymectomy"], "6.5 8.3 15.3": ["regalis"], "4.4 18.6 17.3": ["overridingly"], "9.9 9.9 13.4": ["pacificnewscenter"], "6.1 -2.9 -2.9": ["ecare"], "4.8 11.7 27.6": ["achillea"], "0.9 2.0 9.2": ["dst"], "-4.8 -0.6 8.7": ["tted"], "0.7 1.2 -0.1": ["execu"], "12.9 17.9 19.4": ["univited"], "1.7 2.3 3.0": ["presentaion"], "19.4 11.2 15.3": ["candybars"], "-14.9 5.9 1.2": ["certificant"], "21.1 3.8 25.8": ["braunschweiger"], "0.9 6.4 13.9": ["iday"], "1.3 -4.2 3.2": ["istart"], "4.1 14.3 14.5": ["crist"], "14.9 23.8 8.5": ["killingly"], "8.9 24.9 9.6": ["untag"], "16.6 25.6 17.5": ["supercops"], "5.3 10.2 9.1": ["wreckin"], "10.4 10.6 15.1": ["canula"], "0.9 2.9 11.1": ["kienu"], "7.5 2.8 -0.9": ["registery"], "7.1 -3.8 20.5": ["masterchefs"], "10.0 5.2 7.2": ["toleave"], "6.8 6.7 23.9": ["lablab"], "-3.2 0.4 10.8": ["impromptus"], "1.7 8.6 7.7": ["screechingly"], "1.7 1.5 4.1": ["eop"], "14.3 13.2 24.7": ["beatha"], "0.8 5.7 7.8": ["hemophilic"], "-1.6 18.1 1.7": ["tentmates"], "17.8 11.1 28.0": ["mooses"], "8.8 10.1 12.1": ["loopily"], "5.8 5.2 -0.0": ["fufil"], "4.8 22.6 25.8": ["surfman"], "-4.0 10.5 11.2": ["vicim"], "11.2 1.0 15.3": ["drin"], "3.6 13.6 2.4": ["complaning"], "14.3 7.4 20.2": ["velvetleaf"], "8.4 13.7 6.6": ["poppiness"], "6.0 0.5 12.4": ["tailgrab"], "0.7 -0.7 2.5": ["resitting"], "-1.5 13.1 10.0": ["railers"], "12.3 10.1 31.8": ["samgyetang"], "9.6 -3.1 2.9": ["mobilebroadband"], "6.9 5.4 -7.3": ["lehendakari"], "0.8 21.3 0.5": ["terrorista"], "20.6 7.6 12.4": ["carthorses"], "13.8 -0.8 20.8": ["brasil"], "-4.4 -0.3 4.1": ["mour"], "9.3 5.1 14.4": ["tankered"], "-2.7 13.2 17.9": ["overrace"], "-0.5 6.4 16.0": ["iniisip"], "25.6 12.0 17.3": ["pantlegs"], "6.7 -2.4 17.9": ["hydroxyproline"], "8.0 4.9 9.8": ["trus"], "13.6 11.6 15.5": ["weightily"], "9.7 1.5 7.4": ["rickrolled"], "9.7 11.6 6.7": ["amos"], "4.3 14.5 9.8": ["tanah"], "6.4 2.1 24.7": ["regata"], "20.2 5.0 38.9": ["silverfin"], "8.7 37.3 13.2": ["retalliation"], "15.9 8.5 36.8": ["briney"], "5.7 1.3 5.3": ["macroporous"], "-3.5 8.3 15.7": ["ayoko"], "0.9 19.3 1.0": ["camarilla"], "20.6 21.4 7.9": ["unionbusting"], "5.7 2.2 15.2": ["uremic"], "11.7 2.1 22.0": ["mals"], "7.4 9.0 16.7": ["briary"], "-4.8 15.1 -3.3": ["intiate"], "10.3 -2.4 1.2": ["rosta"], "17.2 5.5 24.1": ["cutleaf"], "4.0 -2.6 12.3": ["amuch"], "-1.0 5.6 4.3": ["highes"], "-8.6 3.1 9.2": ["lowell"], "0.4 11.5 10.8": ["kery"], "-0.6 13.6 3.5": ["strik"], "6.1 20.7 12.1": ["mutators"], "12.0 16.4 11.2": ["afixed"], "5.0 16.9 9.8": ["pulpified"], "17.1 6.5 14.1": ["nestable"], "4.5 9.4 9.5": ["kintu"], "10.0 8.8 11.8": ["zamana"], "12.8 18.3 10.2": ["inverses"], "6.6 12.0 21.8": ["uku"], "3.7 10.3 37.9": ["tidewaters"], "2.7 2.6 11.8": ["fluorotelomers", "increaed"], "3.9 32.4 9.5": ["mililtary"], "-6.9 14.5 6.3": ["personability"], "2.7 3.7 5.3": ["muscian"], "-4.8 0.8 7.5": ["nayi"], "13.3 15.4 37.3": ["lumper"], "-5.8 2.4 -4.9": ["numerary"], "3.4 11.1 10.1": ["photosets"], "5.6 -1.3 14.3": ["vina"], "-4.0 10.9 -1.4": ["vakalatnama"], "2.5 3.8 11.0": ["matrimonio"], "16.2 15.2 21.3": ["caravels"], "4.4 -1.3 8.0": ["cartier"], "24.3 8.8 4.3": ["pureplays"], "2.0 4.2 16.0": ["putnam"], "0.8 -4.4 8.3": ["michel"], "4.2 2.0 5.2": ["pushman"], "-0.7 14.8 6.3": ["cheatsheet"], "11.8 2.7 11.0": ["boites"], "7.2 1.4 10.1": ["purls"], "23.3 6.6 20.6": ["serpentarium"], "12.2 -1.1 23.8": ["mellon"], "3.7 7.8 5.6": ["inother"], "-6.0 9.4 4.3": ["sangham"], "10.0 -14.6 6.1": ["acqui"], "1.0 4.9 6.4": ["drillsite"], "5.6 12.5 12.1": ["sufiana"], "1.2 10.1 3.3": ["monopropellant"], "10.0 12.6 13.3": ["megaregions"], "10.6 29.1 13.7": ["hollowest"], "1.2 14.6 8.8": ["pondoks"], "6.1 8.5 -1.6": ["opned"], "11.0 12.4 14.3": ["isps"], "9.0 -1.4 23.6": ["crispbreads"], "15.5 1.0 31.3": ["ratafia"], "-3.9 19.8 7.4": ["cgolden"], "-1.7 14.4 8.3": ["specking"], "10.1 27.4 11.3": ["impends"], "-1.4 2.4 11.0": ["colonscopy"], "4.4 1.5 -2.5": ["vivatel"], "2.1 9.9 8.6": ["pourasabha"], "-2.0 11.9 7.8": ["paruresis"], "9.5 5.6 16.0": ["rafael"], "-11.5 -7.2 6.6": ["ounty"], "8.8 3.7 8.3": ["groupsets"], "16.5 8.9 21.9": ["ajvar"], "16.0 11.7 17.0": ["shaolin"], "-2.2 0.9 8.2": ["resolicitation"], "15.1 10.6 17.8": ["spectular"], "10.7 0.3 6.6": ["redomiciled"], "3.9 7.5 24.6": ["daiginjo"], "11.0 15.1 -6.6": ["interets"], "12.8 15.7 16.0": ["twighlight"], "-10.3 -3.2 9.3": ["furt"], "2.9 9.7 5.7": ["arund"], "3.7 13.0 21.9": ["jhol"], "13.6 28.0 14.7": ["vincible"], "7.7 12.6 1.6": ["dailykos"], "10.3 2.5 5.2": ["convolutes"], "14.7 6.1 14.4": ["shirtings"], "-4.7 9.1 -6.9": ["toserve"], "8.6 -0.2 -1.0": ["statio"], "19.3 1.0 16.0": ["farolitos"], "12.3 6.4 24.5": ["kilned"], "8.6 0.4 -2.3": ["interoperative"], "16.2 3.9 16.6": ["kerching"], "13.7 9.2 22.6": ["sazerac"], "13.8 24.6 15.6": ["habituates"], "-0.6 21.1 4.9": ["aboslutely"], "14.9 12.2 15.0": ["eductor"], "14.8 17.8 24.2": ["stob"], "2.1 8.6 10.6": ["slav"], "8.4 -10.3 13.0": ["unfinalized"], "3.3 1.8 14.5": ["commentaire"], "10.4 -2.7 12.7": ["doorprizes"], "-4.7 10.0 7.1": ["tthey"], "13.6 9.5 12.4": ["bidon"], "10.8 15.6 31.8": ["redshanks"], "-2.7 13.8 1.5": ["bioenvironmental"], "9.2 -5.7 -4.6": ["fices"], "7.4 14.3 15.5": ["nisl"], "9.1 14.7 29.7": ["chemosynthetic"], "4.8 11.7 16.5": ["adorkable"], "14.8 2.0 0.3": ["remarketer"], "13.1 9.8 27.4": ["moistest"], "2.9 38.1 -1.4": ["unpeople"], "14.9 31.4 20.0": ["shinobi"], "7.0 3.1 13.8": ["checkdams"], "14.6 7.9 2.0": ["microcassette"], "5.4 15.9 10.1": ["bustees"], "4.3 5.9 17.8": ["grubbies"], "12.3 14.4 29.1": ["shmaltz"], "5.2 5.0 6.1": ["riv"], "0.2 1.1 -2.1": ["arabe"], "9.6 21.2 2.7": ["survivers"], "10.5 6.1 5.2": ["themonth"], "14.9 17.1 11.1": ["declivity"], "2.2 8.7 17.1": ["balay"], "4.9 8.8 17.1": ["neurospheres"], "8.4 6.7 -2.4": ["pitcrew"], "-3.0 24.6 2.4": ["policement"], "8.8 24.8 20.0": ["eateth"], "2.2 37.5 9.0": ["adharma"], "3.9 11.7 2.3": ["aspecting"], "7.2 27.8 3.2": ["disarticulate"], "18.8 5.2 16.6": ["overscale"], "-1.8 11.9 13.5": ["ardency"], "9.1 18.6 3.4": ["jural"], "1.4 21.2 6.2": ["fajr"], "3.9 16.3 0.8": ["legitmacy"], "10.3 7.7 35.3": ["paprikas"], "11.6 18.0 11.1": ["restof"], "15.5 11.3 27.7": ["klipspringer"], "5.8 -0.6 1.0": ["aty"], "12.3 5.5 11.6": ["jamz"], "8.7 6.9 10.8": ["inefficiences"], "4.3 4.8 14.0": ["freeholding"], "-1.6 32.7 -2.9": ["qaum"], "6.0 13.1 15.0": ["voxpopulus"], "15.1 12.7 6.4": ["groundsheets"], "3.1 7.6 -0.2": ["awarenes"], "18.5 8.6 23.4": ["slugglish"], "8.9 3.7 23.7": ["bichons"], "9.8 26.2 4.3": ["extremest"], "-1.1 18.1 14.1": ["inteceptions"], "-8.6 -2.7 1.2": ["infomed"], "11.2 16.6 12.8": ["chlorosome"], "4.1 14.9 20.6": ["delightfulness"], "3.5 3.8 8.0": ["profitsharing"], "-1.2 8.5 6.4": ["sereis"], "19.5 20.4 23.5": ["sexers"], "13.3 13.9 7.0": ["werein"], "10.0 8.0 13.3": ["baronesses"], "7.1 18.3 14.2": ["alegedly"], "10.1 3.3 8.3": ["mdf"], "12.3 9.4 12.8": ["yey"], "5.4 13.4 5.5": ["improverished"], "5.1 16.4 16.2": ["overpainting"], "12.8 10.4 2.3": ["galvo"], "7.5 7.9 7.9": ["aramids"], "12.3 13.0 25.0": ["leavener"], "-0.6 -2.7 8.5": ["hanner"], "13.4 12.9 4.0": ["thepower"], "1.2 10.4 1.9": ["windbaggery"], "6.3 2.6 2.3": ["bigbrother"], "12.9 19.6 17.9": ["shant"], "1.2 27.5 1.1": ["talibanisation"], "7.4 -0.1 10.6": ["lactates"], "15.8 16.7 15.2": ["protecter"], "18.4 25.2 22.6": ["dropsault"], "10.9 18.5 12.9": ["huricurana"], "0.4 18.8 7.7": ["shomer"], "-2.4 -2.8 2.9": ["regularizes"], "1.9 19.3 5.9": ["expostulate"], "-1.2 6.7 14.9": ["offdays"], "15.2 6.8 32.8": ["kapusta"], "13.8 16.5 -5.6": ["virutal"], "8.4 5.1 3.8": ["geogrids"], "-8.6 9.3 -3.2": ["hardt"], "2.9 2.6 20.2": ["senora"], "0.2 0.9 8.3": ["propia"], "2.4 15.1 6.2": ["talkgroup"], "15.0 16.5 20.6": ["coldie"], "15.8 3.6 9.3": ["reshingled"], "11.8 7.3 15.4": ["longside"], "0.2 -0.6 13.9": ["nalaman"], "5.0 14.7 12.7": ["kormiko"], "13.4 16.5 23.9": ["eesh"], "22.4 19.2 31.9": ["spookfish"], "18.6 14.5 31.6": ["butta"], "9.1 1.8 7.2": ["imageable"], "17.5 11.5 9.3": ["sodar"], "-6.9 5.0 10.5": ["tigh"], "3.1 4.7 23.8": ["upbound"], "11.5 6.0 40.9": ["patin"], "3.6 -1.8 13.1": ["ymchwiliad"], "3.7 7.1 19.1": ["visitin"], "-3.2 4.5 5.6": ["collaberation"], "9.3 3.4 -1.5": ["jetfuel"], "10.2 6.8 26.1": ["whoopies"], "9.2 5.2 -5.5": ["torwards"], "-9.2 -4.3 10.7": ["classer"], "7.6 17.2 9.2": ["slighest"], "7.4 9.0 23.5": ["oatmeals"], "-6.0 7.9 3.1": ["overcounts"], "17.8 12.0 15.7": ["defat"], "3.1 9.7 15.1": ["kund"], "4.0 1.1 -13.9": ["joinging"], "16.2 22.8 7.8": ["superspies"], "-2.8 3.1 15.0": ["sagot"], "5.5 7.5 4.7": ["judicary"], "12.3 14.0 21.6": ["overrotated"], "-0.5 14.4 4.1": ["acquirements"], "14.5 1.9 11.8": ["duckmaster"], "-0.8 4.1 1.8": ["toreflect"], "12.7 17.5 10.3": ["mirthlessly"], "9.8 13.2 12.3": ["dotingly"], "15.0 12.2 10.4": ["countershaft"], "11.4 19.7 38.0": ["sharptail"], "18.1 9.2 9.3": ["peltier"], "-5.8 16.8 3.0": ["inaptitude"], "11.3 12.5 6.9": ["provincal"], "12.9 11.9 18.9": ["fitz"], "-1.4 19.0 0.3": ["abolutely"], "-0.5 10.5 9.6": ["jimbo"], "2.8 9.3 -1.5": ["oal"], "5.6 17.5 5.0": ["sbj"], "4.7 12.4 11.0": ["occaision"], "8.3 17.4 7.7": ["physicalities"], "8.7 11.7 15.4": ["dimbulb"], "8.9 20.8 1.5": ["jiyalas"], "11.0 17.8 7.0": ["monoplanes"], "0.3 21.4 7.9": ["continious"], "1.8 6.3 15.0": ["rewashing"], "8.9 15.0 18.5": ["jambiya"], "-6.2 6.2 16.6": ["umuwi"], "0.9 16.6 9.4": ["gamechangers"], "14.6 3.5 7.3": ["kaspersky"], "11.8 11.0 -0.4": ["fatest"], "12.2 1.7 9.3": ["digibook"], "7.9 -0.8 7.4": ["tracted"], "6.4 9.5 1.0": ["ision"], "-5.0 7.9 2.7": ["intersystem"], "7.6 18.8 10.4": ["weldment"], "9.3 11.8 16.4": ["orci"], "7.0 12.5 16.6": ["boj"], "7.6 0.9 0.9": ["filedwith"], "1.2 11.5 11.4": ["nicmart"], "14.0 15.2 -0.4": ["comatosed"], "10.9 14.9 21.6": ["restrengthened"], "25.9 8.3 6.0": ["lectric"], "2.9 13.7 15.0": ["beginnin"], "14.8 17.7 14.6": ["jabba"], "7.2 11.1 14.5": ["devta"], "0.3 2.5 6.0": ["metalloprotease"], "14.7 21.7 24.9": ["untasted"], "2.2 5.2 13.4": ["cybrid"], "3.6 0.9 12.3": ["unimodal"], "4.3 18.1 10.8": ["delerium"], "-10.6 1.4 -6.1": ["ective"], "4.7 16.3 5.9": ["disfluency"], "10.2 -6.6 10.9": ["vendita"], "8.4 7.2 -5.8": ["conferance"], "2.2 11.2 -6.6": ["capaign"], "7.9 5.3 20.7": ["kinahanglan"], "2.2 11.2 16.9": ["norite"], "2.1 3.9 14.3": ["grapegrowing"], "16.2 9.2 14.1": ["chubster"], "1.3 18.2 6.8": ["autosaves"], "15.8 15.3 14.5": ["decleated"], "3.5 6.1 10.9": ["hermana"], "22.6 10.3 28.2": ["indri"], "14.9 10.1 4.1": ["predeliction"], "7.9 9.0 8.5": ["slooooow"], "5.9 15.8 1.4": ["havng"], "12.2 2.0 6.1": ["electricy"], "7.2 11.1 13.0": ["morpholino"], "5.4 -1.5 7.0": ["efficace"], "7.2 -8.7 5.4": ["subsized"], "19.6 20.3 14.9": ["jerkoffs"], "-3.3 0.3 -0.3": ["toook"], "10.1 12.0 24.8": ["misadvertised"], "10.5 3.5 6.5": ["applicaiton"], "15.4 3.9 8.2": ["heliospheric"], "-0.1 22.0 4.1": ["nonresistance"], "0.7 0.3 5.1": ["nonprescribed"], "2.9 11.3 -5.1": ["precedessor"], "1.9 12.3 14.2": ["muny"], "9.8 13.4 9.0": ["indivuals"], "12.8 12.0 11.1": ["seizer"], "-7.7 3.6 5.1": ["fructosamine"], "1.5 -3.7 4.9": ["ecma"], "2.4 14.7 -4.9": ["outspokeness"], "8.5 -15.1 -1.1": ["chiefexecutive"], "8.6 24.7 5.4": ["mutaween"], "2.8 6.4 18.0": ["elaine"], "11.0 22.7 5.8": ["kizuna"], "7.2 10.8 10.9": ["teratology"], "-5.4 4.6 11.1": ["undermentioned"], "19.2 2.8 14.5": ["washstands"], "8.6 1.8 21.0": ["trimethylamine"], "17.1 8.6 16.2": ["splatterings"], "8.3 0.9 15.3": ["coozies"], "-0.3 5.4 4.1": ["ulimorelin"], "22.6 26.7 16.7": ["unsheath"], "3.1 -3.9 7.1": ["miligram"], "5.5 20.9 0.7": ["annoyingness"], "12.6 19.3 5.0": ["illusional"], "14.5 13.6 23.7": ["spalled"], "12.9 6.1 21.2": ["tanoa"], "15.9 -1.7 15.5": ["sidney"], "4.3 -1.3 6.5": ["besten"], "17.2 17.7 10.3": ["prettyboy"], "-3.2 2.0 3.4": ["thelead"], "7.8 5.9 1.6": ["toplevel"], "2.0 14.6 1.6": ["reversely"], "16.1 10.9 18.1": ["sepal"], "2.4 17.2 14.3": ["unrefreshed"], "9.4 2.5 24.6": ["qiviut"], "-3.5 15.8 1.4": ["bloviates"], "8.9 3.0 8.8": ["operativo"], "9.5 -10.0 8.4": ["millionfrom"], "14.1 10.5 22.4": ["washrag"], "-1.7 1.4 7.5": ["cycloaddition"], "-0.1 -4.7 5.9": ["takeplace"], "-3.5 0.9 2.4": ["classrom"], "21.9 3.8 20.7": ["highstakes"], "7.1 9.5 31.9": ["catboats"], "9.0 2.4 8.3": ["ovale"], "11.9 11.0 21.1": ["burmese"], "7.5 14.0 18.0": ["filthily"], "10.8 28.8 19.3": ["celestials"], "21.4 26.9 17.4": ["bigass"], "7.0 16.7 8.9": ["afrocentric"], "6.3 9.8 25.4": ["subpolar"], "9.2 25.6 17.4": ["asymptote"], "-0.7 12.1 9.7": ["apdenver"], "1.0 5.7 10.0": ["supraclavicular"], "20.3 8.6 11.8": ["aquarter"], "0.8 2.9 0.8": ["tpb"], "9.1 11.2 9.8": ["instantaneity"], "2.6 7.5 13.4": ["mssing"], "0.0 3.8 -7.9": ["bellavistapoa"], "6.8 12.2 10.1": ["handwheel"], "-1.0 13.4 6.0": ["photopigment"], "20.8 10.3 19.7": ["behatted"], "4.4 -1.3 22.4": ["snowsnake"], "-2.3 7.9 5.7": ["asar"], "19.5 8.9 13.1": ["swanny"], "-7.1 8.2 7.6": ["isoenzyme"], "7.1 18.1 8.7": ["interocular"], "7.9 6.0 3.5": ["gubenatorial"], "15.9 13.9 14.1": ["doglegged"], "10.1 19.8 -1.1": ["doublecross"], "8.2 2.8 6.0": ["messe"], "-2.7 7.6 8.4": ["cmm"], "-0.9 18.4 2.1": ["rubab"], "12.6 5.9 9.4": ["phenomenol"], "15.7 0.0 4.6": ["micromotors"], "24.3 13.7 3.6": ["stereogram"], "2.4 12.7 1.1": ["majermanes"], "3.1 19.1 6.7": ["cannont"], "23.3 20.7 21.1": ["gimble"], "5.7 11.6 10.7": ["dharana"], "4.2 16.0 5.2": ["godfathered"], "0.8 5.4 8.4": ["babalawo"], "6.1 -0.7 -0.5": ["oard"], "3.8 6.0 7.7": ["dinotefuran"], "-4.1 -0.1 -2.4": ["extranodal"], "2.0 -1.1 1.2": ["fforwm"], "3.3 18.7 7.6": ["brahminical"], "5.0 9.9 9.4": ["prepartions"], "3.1 4.0 7.4": ["glomerulosclerosis"], "19.3 2.5 15.2": ["coolbox"], "11.6 21.7 18.2": ["mossbacks"], "10.2 6.5 13.1": ["denna"], "5.7 7.1 4.1": ["diapason"], "17.1 17.9 23.1": ["lizzie"], "11.7 16.5 8.5": ["arabia"], "2.2 3.1 19.9": ["mezcals"], "22.8 21.3 5.8": ["bypassers"], "11.1 4.6 6.2": ["insurees"], "8.4 6.0 3.6": ["envisoned"], "9.2 2.1 18.2": ["bouillons"], "13.0 2.2 9.2": ["sigmoidoscope"], "10.3 19.9 16.3": ["virga"], "-0.3 4.1 1.9": ["pregancies"], "7.8 14.7 8.4": ["piggishness"], "0.1 3.6 8.1": ["halfmarathon"], "14.6 12.1 10.5": ["gallerygoers"], "12.3 10.7 17.4": ["methanogenesis"], "28.0 6.8 8.7": ["bigggest"], "1.4 -2.1 3.7": ["themajority"], "3.9 3.7 8.7": ["calligraphist"], "0.7 6.2 -5.7": ["monitered"], "18.4 14.4 10.8": ["competiion"], "14.1 18.4 4.7": ["interal"], "2.0 -0.7 -8.3": ["officialised"], "15.9 6.8 10.9": ["colourfulness"], "-2.0 7.8 4.5": ["reiserfs"], "12.7 -0.1 13.5": ["includi"], "1.1 -2.4 6.3": ["peryear"], "10.4 6.0 9.6": ["pyrophyllite"], "8.2 3.4 5.8": ["lakshmi"], "24.8 12.5 33.5": ["metate"], "1.9 -2.7 0.3": ["beia"], "6.3 0.9 8.1": ["retailored"], "2.9 2.1 4.9": ["selfservice"], "5.1 5.3 1.9": ["mbc"], "8.0 18.0 7.6": ["palimpsests"], "1.0 9.8 5.9": ["localite"], "14.5 11.1 3.3": ["ultrasharp"], "21.9 5.8 15.1": ["grouchiest"], "4.5 6.1 7.4": ["thulium"], "25.2 20.6 16.4": ["viselike"], "10.0 0.7 26.9": ["salata"], "8.7 2.1 0.3": ["scuderia"], "5.0 15.4 15.5": ["masuk"], "8.3 0.5 3.0": ["serveur"], "11.5 5.7 18.1": ["faffed"], "17.9 19.2 15.7": ["manspace"], "8.2 14.9 12.4": ["lekar"], "9.2 7.2 9.1": ["milies"], "8.1 15.5 13.4": ["alwys"], "2.5 1.6 2.0": ["raed"], "7.0 16.7 5.9": ["oganisation"], "1.9 5.7 18.3": ["sikat"], "11.6 6.8 6.8": ["reapproached"], "4.6 13.3 12.7": ["gotto"], "10.0 18.6 19.1": ["sankofa"], "9.5 10.3 16.4": ["rammers"], "1.9 5.2 6.1": ["inernational"], "9.8 8.9 8.6": ["briggs"], "10.1 11.9 20.8": ["usta"], "1.8 -4.7 12.9": ["coggins"], "10.2 14.0 22.8": ["hok"], "15.3 18.7 10.0": ["microshutters"], "19.2 9.8 20.1": ["penholders"], "7.8 8.5 9.0": ["kommende"], "2.5 11.0 7.1": ["carrries"], "0.7 11.0 11.3": ["idhar"], "7.1 11.9 3.7": ["awoman"], "5.5 7.1 11.8": ["vlc"], "0.5 16.7 9.7": ["elderspeak"], "7.4 9.8 2.9": ["fullly"], "4.6 12.3 9.4": ["andhow"], "14.5 15.0 15.7": ["ectodermal"], "11.0 -0.3 22.9": ["lait"], "18.4 11.3 17.2": ["meeeee"], "12.0 7.1 30.7": ["clarkia"], "20.9 -4.5 17.8": ["drinkery"], "1.3 11.3 18.0": ["buffalograss"], "12.0 8.9 14.4": ["kyanite"], "15.9 6.1 12.5": ["predrilled"], "13.2 -5.9 2.9": ["crossmedia"], "6.7 15.9 12.5": ["telluric"], "3.1 16.0 1.4": ["financialy"], "14.1 8.7 11.0": ["frowzy"], "19.0 10.1 26.7": ["schwarma"], "-6.1 -0.4 -6.8": ["printservices"], "18.5 13.2 10.8": ["jockies"], "1.2 5.3 13.9": ["masasabi"], "6.4 20.6 1.4": ["prisoned"], "1.9 15.7 7.4": ["overgeneralizations"], "2.8 1.6 -1.2": ["desludging"], "11.6 13.3 1.9": ["bringen"], "4.7 25.4 11.9": ["simunitions"], "10.5 18.8 9.9": ["malema"], "7.0 -5.5 2.4": ["tobegin"], "12.8 7.7 19.6": ["brae"], "11.2 10.3 1.4": ["intexticated"], "16.8 8.5 8.7": ["sharholders"], "-0.8 3.4 10.8": ["panchayath"], "-6.6 6.2 4.4": ["pretermitted"], "12.9 6.8 -2.4": ["thesuccess"], "7.2 0.4 -1.9": ["beurs"], "3.7 0.7 16.2": ["farmstay"], "0.1 2.5 15.5": ["tylosin"], "7.8 15.2 1.1": ["highvalue"], "8.4 -1.8 11.5": ["ecoroofs"], "9.7 13.9 29.6": ["barako"], "10.3 20.2 15.8": ["rinos"], "15.1 6.2 0.4": ["globalleader"], "-2.0 6.0 1.9": ["scintigraphic"], "5.5 17.8 13.7": ["seeminly"], "8.0 20.5 4.8": ["pikestaff"], "13.4 -7.3 11.0": ["scherenschnitte"], "2.2 17.8 8.4": ["dissapointments"], "10.9 14.1 12.5": ["cubans"], "12.4 -3.5 -3.2": ["yearsin"], "16.4 7.0 16.0": ["cinematical"], "11.4 4.3 4.0": ["ustralia"], "18.7 11.6 14.0": ["czarinas"], "-3.8 7.8 8.1": ["tangency"], "7.4 13.7 6.4": ["randomising"], "7.3 4.4 5.7": ["ske"], "12.4 17.6 3.7": ["jailmate"], "1.2 3.1 10.2": ["asthmas"], "17.2 10.5 28.3": ["porkchops"], "-1.5 8.5 4.4": ["ennis"], "0.1 11.6 0.6": ["philosophe"], "20.6 7.9 13.5": ["dasherboards"], "22.2 6.8 15.0": ["stell"], "10.5 7.8 11.0": ["ofbeing"], "15.6 8.2 21.9": ["jalousie"], "30.1 11.4 23.8": ["adamastor"], "1.2 10.6 6.4": ["incometax"], "10.8 24.9 14.8": ["anthropomorphise"], "15.1 26.3 13.1": ["krumpers"], "0.2 12.9 7.4": ["keeped"], "-0.3 11.2 9.0": ["coinfections"], "-1.4 12.6 12.2": ["makipag"], "9.6 12.0 17.3": ["parva"], "7.8 33.3 9.4": ["cannoneers"], "17.5 16.9 28.8": ["wingbeats"], "8.6 28.4 12.0": ["underminer"], "-2.1 5.2 -4.5": ["lise"], "-0.9 10.1 14.5": ["phalaris"], "-4.1 2.3 0.6": ["fidei"], "1.0 8.0 3.6": ["ebenfalls"], "11.8 30.6 9.2": ["theattack"], "7.9 16.2 19.1": ["nowheres"], "1.1 10.8 12.6": ["othewise"], "19.1 22.9 0.8": ["planeful"], "12.3 9.8 2.3": ["prescripted"], "21.2 9.3 22.2": ["parrothead"], "24.2 4.4 7.8": ["protype"], "2.5 9.6 10.7": ["residencia"], "2.4 -1.2 8.4": ["accrediation"], "18.2 -0.3 35.2": ["keftedes"], "2.7 12.3 0.5": ["contnue"], "2.1 21.3 0.8": ["undenied"], "4.5 4.0 17.9": ["halimbawa"], "9.5 5.9 11.0": ["vedere"], "1.9 15.2 4.3": ["thesystem"], "2.8 -7.8 -3.1": ["analsyt"], "7.5 6.9 13.4": ["moyamoya"], "18.1 12.7 3.9": ["coutnries"], "11.7 3.3 10.1": ["conducter"], "10.4 1.4 10.1": ["multievent"], "10.8 6.9 17.8": ["cityfolk"], "18.6 -9.1 -2.2": ["consultantcy"], "9.9 6.1 -0.3": ["cardiograms"], "7.1 -1.6 18.1": ["homecraft"], "8.2 3.6 11.5": ["mycket"], "-1.6 23.4 4.6": ["significations"], "0.2 30.8 -1.9": ["sigint"], "18.8 32.9 11.4": ["dementor"], "27.8 9.9 21.1": ["bungeed"], "6.1 1.2 11.9": ["isoprenoid"], "-4.3 5.9 12.3": ["teachin"], "4.5 6.1 24.0": ["tso"], "2.5 -4.6 15.1": ["pounts"], "4.1 9.1 10.1": ["methanogen"], "0.4 9.4 12.6": ["glatt"], "2.8 0.8 14.0": ["prepacking"], "10.4 14.2 4.8": ["organizatons"], "5.0 24.5 12.8": ["blissfulness"], "5.1 6.7 7.0": ["folacin"], "3.0 2.8 13.3": ["regrip"], "1.5 9.3 8.0": ["adventitia"], "6.3 23.6 7.1": ["inerasable"], "7.7 7.0 15.2": ["barnett"], "2.8 6.9 6.1": ["scrutineered"], "0.8 19.3 4.1": ["pedestrains"], "8.1 10.9 0.2": ["biopolitics"], "6.9 9.2 12.5": ["endogamous"], "-1.5 -1.0 -2.2": ["airplays"], "4.6 13.6 9.5": ["hoodrat"], "1.2 -0.3 3.5": ["cois"], "11.6 9.3 29.6": ["lasagnes"], "9.8 6.5 17.0": ["jetboating"], "7.2 21.8 13.8": ["everythng"], "4.6 14.8 10.5": ["superfluities"], "10.4 25.5 14.2": ["constanly"], "11.4 5.4 31.1": ["hali"], "12.0 12.7 24.9": ["longifolia"], "2.2 2.7 6.6": ["answerscripts"], "13.3 4.6 21.8": ["jugged"], "10.1 4.0 13.9": ["nished"], "-1.2 15.1 7.6": ["purana"], "2.2 14.6 13.1": ["bantay"], "15.9 1.6 2.8": ["oled"], "0.0 0.2 8.7": ["pushability"], "5.5 7.2 17.5": ["bret"], "1.3 -7.5 12.2": ["tsaka"], "5.3 7.5 7.0": ["quadruplicate"], "9.7 15.0 6.7": ["distained"], "17.0 7.2 13.0": ["spongebob"], "-3.7 23.2 1.3": ["tzadik"], "3.8 10.4 11.3": ["cahill"], "7.6 17.0 14.5": ["goosepimples"], "6.9 14.3 15.7": ["malaysians"], "1.6 15.2 0.2": ["malintent"], "1.8 6.7 16.2": ["selamat"], "-0.5 9.6 -4.2": ["amde"], "26.1 5.6 -0.3": ["kinetoscope"], "4.1 16.4 4.3": ["rnc"], "10.6 -4.6 4.8": ["newsalistic"], "-1.2 4.9 7.7": ["groupes"], "6.5 11.1 15.2": ["kaisa"], "17.3 11.3 33.0": ["flatfishes"], "-2.4 4.5 11.2": ["tricaptain"], "-1.8 6.8 11.0": ["steepener"], "7.4 16.5 18.0": ["onehanded"], "8.3 2.5 7.6": ["musuems"], "4.6 8.7 18.0": ["staccatos"], "5.5 5.4 10.7": ["budg"], "17.5 13.0 10.5": ["nauts"], "8.2 26.0 11.6": ["unuseful"], "2.5 1.5 6.1": ["unpatentability"], "3.8 6.8 0.6": ["arecurrently"], "7.1 5.1 9.8": ["nsf"], "-2.5 13.1 1.4": ["sraight"], "4.6 5.3 13.2": ["leonardo"], "9.8 22.9 10.6": ["immovability"], "10.5 24.1 12.3": ["leadeth"], "14.8 23.0 10.9": ["fucktards"], "7.3 23.5 -1.5": ["ensconces"], "1.9 12.5 6.1": ["monogamists"], "8.1 -5.4 14.8": ["oca"], "13.2 4.4 20.1": ["noc"], "4.2 12.9 2.4": ["faultered"], "-0.2 27.3 4.3": ["gunfires"], "6.3 3.9 13.7": ["oxi"], "9.8 1.1 3.2": ["wonojo"], "7.0 3.0 12.7": ["navratri"], "0.6 -0.3 -2.7": ["softproofing"], "4.1 15.8 7.5": ["sentimentalizes"], "-1.3 3.9 13.3": ["addysg"], "10.9 2.2 20.1": ["resturaunt"], "5.4 12.8 3.5": ["feedreader"], "9.2 16.2 4.2": ["boxout"], "12.1 15.5 11.1": ["oflife"], "-6.2 1.8 7.1": ["hospi"], "12.7 9.8 -0.5": ["horsebacks"], "19.1 12.0 0.8": ["monopolistically"], "10.7 7.1 12.0": ["sarcophaguses"], "4.0 -1.4 3.9": ["recognitio"], "12.9 20.0 16.8": ["fighty"], "2.7 1.0 1.8": ["kgbdeals"], "-1.5 -3.5 10.3": ["tricounty"], "2.6 10.2 6.6": ["roadracer"], "14.0 8.8 22.5": ["cyclospora"], "6.6 -2.2 8.6": ["payrises"], "-4.9 -7.2 4.2": ["resuts"], "4.4 9.4 4.5": ["changement"], "6.6 17.5 -1.6": ["eurosceptical"], "6.8 9.8 21.8": ["jughandles"], "20.2 15.8 18.1": ["sundog"], "17.0 6.3 16.0": ["sharked"], "3.4 9.7 -6.2": ["picometers"], "4.4 4.0 -0.8": ["hosteller"], "-0.2 -0.6 -1.7": ["notetakers"], "1.8 18.3 4.7": ["messge"], "6.5 13.9 20.8": ["eephus"], "0.6 22.9 11.1": ["paleocon"], "-2.3 17.2 2.0": ["blackmailable"], "1.3 20.0 -2.8": ["imprisioned"], "8.7 6.3 23.1": ["pithas"], "17.9 5.8 10.0": ["sparkliest"], "12.4 9.5 48.0": ["dorade"], "7.8 7.9 -2.8": ["fls"], "8.3 6.2 14.1": ["dekhne"], "19.0 18.6 9.4": ["deindustrialized"], "12.5 13.0 10.1": ["plo"], "-6.7 2.3 9.7": ["conact"], "2.2 17.1 16.1": ["rickettsial"], "11.9 5.2 5.9": ["sliproads"], "1.8 -7.7 12.9": ["troh"], "2.8 21.4 11.1": ["deadlined"], "2.0 12.1 16.5": ["babesia"], "16.3 14.1 21.6": ["mesomorph"], "-5.2 4.5 9.3": ["quist"], "8.6 1.0 12.4": ["safter"], "0.5 0.8 2.0": ["palced"], "-3.8 4.0 8.1": ["mandolinists"], "10.2 9.9 11.1": ["peaceline"], "-2.8 10.5 9.5": ["qualityof"], "16.4 2.7 32.4": ["chipolte"], "-4.3 18.7 10.7": ["subgoals"], "10.1 8.3 8.2": ["vedio"], "14.6 3.2 10.9": ["fallopian"], "13.9 32.2 16.9": ["keyblade"], "-2.1 3.1 -0.1": ["minte"], "6.6 13.7 14.2": ["armbreaker"], "4.6 -3.2 1.1": ["reprot"], "12.8 23.1 8.4": ["hardpoints"], "11.8 15.4 27.8": ["aculeatus"], "11.0 8.6 9.2": ["djellabas"], "6.4 -2.3 8.7": ["pped"], "7.2 15.1 15.9": ["pagri"], "-0.5 -7.4 8.0": ["nuhs"], "1.9 3.0 -1.8": ["paybill"], "14.3 0.8 11.5": ["clyde"], "9.4 19.1 7.5": ["attachement"], "1.9 6.5 10.9": ["gunn"], "12.5 14.8 9.8": ["buttom"], "0.8 9.6 13.4": ["medipot"], "14.1 7.7 18.9": ["armstand"], "-2.2 5.7 1.8": ["parlament"], "12.5 16.1 4.4": ["cinemaphiles"], "-2.4 -0.2 -0.1": ["cowrite"], "3.7 5.6 2.3": ["thourough"], "-12.3 12.3 8.7": ["tithers"], "16.6 10.1 13.3": ["aaargh"], "18.6 9.4 5.1": ["imagemakers"], "-0.9 0.5 -2.1": ["thematter"], "8.4 18.1 19.5": ["drowse"], "6.0 4.1 22.7": ["thaali"], "11.1 1.8 11.0": ["plethoric"], "7.6 4.5 0.3": ["monocab"], "9.5 7.8 15.0": ["sien"], "5.4 1.3 9.6": ["playparks"], "-4.6 3.3 0.4": ["fts"], "6.2 4.1 11.9": ["offive"], "-8.1 5.9 2.2": ["rior"], "6.6 -4.0 9.4": ["tess"], "0.3 3.3 6.9": ["dystrophies"], "9.0 18.7 19.5": ["nuffink"], "10.3 9.3 9.0": ["ecotechnology"], "4.1 3.9 0.5": ["reediting"], "-9.2 -2.6 2.5": ["readvertising"], "-1.7 14.5 1.3": ["highscoring"], "10.1 0.1 8.3": ["ballpens"], "-1.2 -5.3 1.6": ["communitisation"], "7.8 16.2 10.6": ["unfettering"], "-1.9 14.2 3.6": ["priorties"], "-10.4 2.1 5.6": ["reindict"], "11.8 -1.1 11.1": ["perce"], "20.9 9.4 23.7": ["globesity"], "2.4 19.0 8.0": ["carefuly"], "6.9 4.9 17.6": ["dadda"], "12.3 17.0 12.3": ["headshakes"], "8.4 8.7 7.1": ["derivitive"], "-2.2 0.9 11.6": ["batgirl"], "-4.0 13.6 12.2": ["senso"], "3.8 -1.6 6.8": ["tickerspy"], "12.2 7.9 11.4": ["shiloh"], "5.2 10.2 15.3": ["lumalabas"], "0.9 9.2 8.5": ["ethnicised"], "10.0 18.5 13.3": ["overstride"], "-0.8 3.8 8.8": ["mmscfpd"], "12.5 9.3 13.4": ["perty"], "2.5 3.5 4.6": ["bion"], "7.0 2.9 1.3": ["peor"], "8.2 14.7 8.9": ["reticently"], "2.3 27.0 14.1": ["wante"], "6.6 8.6 13.1": ["protectress", "dharti"], "2.4 15.7 16.5": ["gamethread"], "-3.4 6.2 16.9": ["kabir"], "-6.8 4.4 2.8": ["neuropathologists"], "28.0 18.8 28.9": ["candiru"], "-3.3 15.2 9.9": ["subchapters"], "13.3 6.6 2.7": ["unviewed"], "0.1 -0.6 13.1": ["subprecinct"], "3.5 15.2 3.8": ["clientelistic"], "6.8 5.0 7.7": ["openssh"], "5.7 5.7 19.8": ["pangarap"], "-4.7 2.0 2.9": ["unat"], "0.2 7.4 7.7": ["pyroxenites"], "7.8 2.3 5.0": ["toodling"], "9.3 5.3 40.2": ["longfins"], "4.0 12.1 10.9": ["overborrow"], "16.8 -0.5 5.4": ["compter"], "5.4 15.4 7.4": ["communitiy"], "-2.0 6.8 8.1": ["redelineation"], "-0.2 7.5 7.2": ["dzikir"], "23.9 7.3 21.1": ["minnie"], "7.6 13.7 10.2": ["deservedness"], "6.1 2.1 8.1": ["oncourse"], "2.3 7.5 16.8": ["gallagher"], "2.8 1.4 4.6": ["tosday"], "22.6 12.8 17.6": ["tumbrel"], "6.9 9.1 17.2": ["anang"], "10.4 7.1 3.0": ["relie"], "0.5 3.1 3.9": ["rotax"], "10.3 10.3 18.3": ["hsu"], "-1.5 6.4 1.4": ["sumed"], "3.7 4.0 -1.6": ["coursebook"], "20.1 23.5 13.0": ["pigmies"], "-1.3 19.7 6.8": ["midranking"], "-2.4 10.0 16.2": ["shari"], "4.3 5.5 -2.0": ["iglide"], "-5.5 -11.5 -2.9": ["tants"], "2.7 9.2 1.2": ["peopple"], "15.7 10.4 29.8": ["kelong"], "4.7 13.8 -3.3": ["orgnization"], "6.2 0.3 2.5": ["directamente"], "8.5 7.1 14.9": ["photocontest"], "4.2 12.6 4.9": ["discimination"], "8.1 11.6 11.1": ["geologies"], "-3.3 17.9 8.8": ["soberer"], "9.8 6.1 7.9": ["dedusting"], "11.2 14.3 34.2": ["waveless"], "-3.8 20.1 0.2": ["inapproriate"], "5.9 3.6 12.8": ["craftsmanlike"], "15.1 11.2 -0.1": ["chuntered"], "7.2 6.4 21.5": ["pelletised"], "10.4 14.2 13.9": ["polyploids"], "8.8 5.0 27.3": ["panaderia"], "8.0 -6.8 2.3": ["esearch"], "8.8 3.6 36.2": ["jonnycakes"], "18.9 25.1 10.6": ["recarve"], "15.5 3.9 -3.0": ["denationalised"], "7.1 2.1 10.6": ["mmscm"], "11.8 8.8 18.2": ["potholers"], "7.8 8.7 9.5": ["invocatory"], "-3.9 5.3 16.4": ["decrim"], "5.5 5.9 11.4": ["dorsi"], "10.1 -0.3 6.1": ["deskless"], "1.9 5.5 2.3": ["pesification"], "4.6 3.6 10.2": ["midis"], "-0.7 5.9 10.3": ["iliopsoas"], "16.4 18.6 8.8": ["psychokinetic"], "1.5 9.2 8.3": ["unning"], "7.0 8.6 16.6": ["larging"], "11.3 9.5 5.2": ["practially"], "3.0 10.2 2.4": ["discloseable"], "1.1 7.1 3.6": ["aggregative"], "4.2 4.7 9.0": ["psychopharmacologic"], "21.8 11.8 13.9": ["patchers"], "9.8 -0.1 33.8": ["peperoncino"], "18.0 8.0 22.4": ["grinner"], "14.4 5.2 14.3": ["lampblack"], "8.7 -5.6 5.9": ["breastpump"], "-3.7 4.5 2.0": ["acetominophen"], "7.8 5.1 -6.4": ["analyist"], "14.0 5.4 1.5": ["cannel"], "21.8 3.4 0.2": ["galvanometer"], "5.3 18.3 -1.5": ["unsuccessfuly"], "3.8 19.4 4.6": ["offcers"], "0.4 23.2 3.3": ["shias"], "11.7 16.0 8.2": ["dymanic"], "7.5 0.1 11.5": ["harware"], "10.7 7.4 19.4": ["regia"], "14.6 14.1 6.1": ["superstrings"], "0.5 0.4 12.9": ["vacances"], "16.5 14.5 12.8": ["razer"], "-0.2 8.9 2.4": ["revisable"], "6.8 -0.3 11.7": ["fonctions"], "11.4 17.1 19.0": ["abrades"], "3.0 9.5 6.6": ["jatras"], "2.4 16.5 4.7": ["microsleep"], "11.2 6.7 9.0": ["multifilament"], "10.4 3.0 24.5": ["lamby"], "-1.8 2.0 -0.3": ["zaf"], "4.0 1.8 6.4": ["disincentivising"], "-6.9 -7.4 5.7": ["cating"], "10.0 9.7 11.8": ["tiyaga"], "5.2 3.4 2.2": ["ssing"], "10.8 30.4 9.5": ["darknesses"], "15.9 14.5 10.3": ["polyhedrons"], "22.7 11.4 12.3": ["gaslit"], "4.4 18.8 3.1": ["outr"], "6.7 -4.4 22.6": ["swimfest"], "-2.1 17.1 11.7": ["disheartenment"], "6.4 10.8 11.0": ["pucked"], "16.2 2.8 17.4": ["brazilwood"], "0.9 5.9 19.5": ["bilities"], "0.1 12.9 16.0": ["indivudual"], "-0.1 2.1 9.1": ["essen"], "13.0 15.8 24.9": ["sleeted"], "0.6 8.0 5.0": ["wagonmaster"], "6.1 3.5 16.3": ["multistrand"], "1.5 -0.1 10.5": ["verdi"], "6.3 18.0 14.9": ["irrepressibility"], "19.7 17.3 11.2": ["frontmost"], "8.1 18.9 18.8": ["bilharzias"], "0.5 2.9 6.7": ["varactors"], "18.6 15.4 19.1": ["jaffas"], "-2.9 13.8 18.8": ["watchkeeping"], "4.7 33.2 4.1": ["ideaology"], "22.1 21.2 15.8": ["werehog"], "7.0 2.7 9.7": ["reattribute"], "7.5 6.8 11.2": ["anser"], "19.6 25.8 13.0": ["purposelessly"], "10.9 17.6 32.0": ["blueys"], "17.5 10.8 28.7": ["brewsky"], "3.6 17.8 2.1": ["communalize"], "-2.8 -4.2 3.1": ["ule"], "10.9 5.8 19.2": ["khet"], "6.3 1.3 1.9": ["focues"], "10.5 15.8 3.2": ["betokened"], "12.8 -2.0 10.9": ["typcial"], "-6.0 7.0 7.1": ["grandfamilies"], "13.4 12.1 15.4": ["proteorhodopsin"], "5.2 2.8 20.5": ["lakas"], "6.4 17.2 25.8": ["oshanas"], "12.6 -7.2 3.9": ["stitchless"], "0.3 3.8 6.4": ["reconsecration"], "14.3 15.5 4.6": ["deodoriser"], "4.5 4.4 2.1": ["scottsdale"], "-1.4 15.4 1.8": ["institutionalists"], "-4.2 5.6 9.2": ["metachronous"], "12.9 -4.3 20.5": ["caine"], "4.0 6.5 11.8": ["granodiorites"], "15.2 9.7 4.0": ["megaproducer"], "4.0 11.3 8.7": ["bumsters"], "18.0 10.4 13.9": ["bimbettes"], "7.0 7.2 5.4": ["actividades"], "1.8 1.0 12.7": ["tawag"], "2.7 8.2 14.4": ["anga"], "12.3 2.7 39.6": ["laulau"], "16.0 15.9 26.2": ["spagetti"], "9.4 1.2 4.4": ["followspots"], "3.6 2.2 3.5": ["admissability"], "9.4 7.0 7.9": ["bambeco"], "11.2 14.7 31.4": ["swordtails"], "-3.5 7.5 11.0": ["pansin"], "3.8 7.8 10.0": ["reprintings"], "-2.7 12.1 10.0": ["housegirl"], "4.7 19.6 8.9": ["duhh"], "10.0 4.4 1.7": ["lossses"], "8.5 34.3 10.3": ["globalisers"], "6.0 21.7 6.2": ["inactively"], "14.0 5.4 17.5": ["ovenight"], "-2.2 15.9 6.0": ["inlining"], "13.6 12.7 12.6": ["homologies"], "6.2 13.3 13.4": ["levelness"], "16.6 11.1 33.1": ["hoverfly"], "0.7 25.2 2.4": ["shahadah"], "10.1 1.2 4.0": ["tanaiste"], "1.3 3.0 3.1": ["printcom"], "10.3 2.0 8.6": ["cual"], "13.3 5.7 14.6": ["icemaking"], "7.0 10.2 15.9": ["unmating"], "13.6 10.7 13.4": ["nondancers"], "12.7 10.3 11.8": ["cammed"], "5.0 14.4 11.0": ["emotiveness"], "14.1 3.4 44.5": ["omena"], "20.6 21.6 14.3": ["pixelating"], "13.9 10.5 12.0": ["shockumentary"], "-0.2 15.6 14.5": ["cakap"], "14.3 6.9 2.1": ["inoperational"], "1.5 14.3 6.3": ["wrapt"], "4.9 -6.4 13.5": ["dairyfarmers"], "17.9 3.0 30.0": ["sope"], "2.6 9.8 15.8": ["famili"], "16.6 18.9 12.7": ["cybergangs"], "4.2 11.3 5.0": ["lefter"], "4.6 18.5 9.0": ["virosomes"], "11.9 -1.4 9.4": ["merck"], "4.6 20.7 12.1": ["urbans"], "6.8 7.8 13.8": ["rakija"], "8.3 9.7 14.3": ["prolapses"], "10.0 0.1 8.2": ["toshareholders"], "20.2 10.7 18.5": ["calavera"], "9.9 8.4 13.5": ["shimmeringly"], "1.5 -2.6 5.6": ["seved"], "1.1 -3.2 0.6": ["apearances"], "6.9 19.4 11.8": ["macd"], "10.8 23.7 13.2": ["everying"], "0.9 6.2 -1.4": ["republications"], "-1.6 7.2 9.4": ["enobytes"], "4.2 10.6 6.6": ["thouse"], "-4.1 1.0 16.0": ["estudyante"], "-0.6 9.1 13.0": ["lalong"], "20.1 31.9 11.5": ["demoniacal"], "1.7 2.1 11.3": ["backloads"], "13.6 14.3 15.1": ["fuelish"], "0.7 5.6 17.1": ["yates"], "-3.5 14.4 0.6": ["dissimilarly"], "10.5 4.2 11.5": ["semin"], "1.8 1.4 14.4": ["boun"], "-5.4 12.7 0.0": ["qazaf"], "15.7 13.6 13.4": ["scorpio"], "-2.0 12.4 -3.2": ["distabilise"], "1.3 -2.1 -5.4": ["acp"], "-0.5 10.9 10.4": ["reinter"], "4.7 11.5 6.3": ["kumi"], "19.6 -5.3 8.4": ["egovernance"], "8.9 12.6 16.8": ["chod"], "14.3 0.9 9.7": ["encapsulator"], "23.9 9.4 22.6": ["roulettes"], "18.2 11.1 15.9": ["rajahs"], "-1.8 -6.0 0.8": ["dvb"], "14.6 12.6 5.3": ["bleek"], "15.6 13.1 20.8": ["pinus"], "5.8 1.7 5.3": ["noncontrolled"], "-1.7 10.2 6.7": ["glucocerebroside"], "5.3 16.7 2.5": ["dicision"], "7.5 16.2 9.4": ["oys"], "22.2 0.6 6.5": ["investements"], "11.5 7.1 9.9": ["hogy"], "2.4 9.0 5.4": ["internationaly"], "2.9 3.2 8.0": ["telah"], "19.4 2.1 19.3": ["offy"], "1.9 8.5 -0.4": ["notbeen"], "-1.5 5.8 10.3": ["timeof"], "4.1 28.4 2.9": ["cheatings"], "-6.5 1.8 5.4": ["micah"], "18.5 18.0 15.6": ["redrum"], "1.2 -6.0 8.1": ["jeudi"], "10.0 9.9 11.5": ["percussiveness"], "11.8 14.4 9.7": ["tweetin"], "1.9 -0.7 1.0": ["erman"], "8.2 26.2 13.1": ["peradventure"], "3.7 6.6 8.5": ["cba"], "5.4 14.9 10.9": ["fayetteville"], "6.6 -3.3 6.7": ["itinery"], "2.3 14.2 9.4": ["excactly"], "-0.6 14.0 12.3": ["momment"], "4.2 16.9 9.1": ["andyou"], "5.7 8.8 11.7": ["optimstic"], "-10.0 -4.6 6.0": ["specialneeds"], "4.8 4.2 6.8": ["evacauted"], "9.1 11.9 6.7": ["rearticulate"], "-2.1 9.4 4.3": ["forborne"], "10.5 28.3 2.8": ["loathsomeness"], "16.1 15.5 4.0": ["pussyfooted"], "15.6 -0.3 39.0": ["gnocci"], "0.2 11.8 -0.7": ["simplifier"], "8.9 4.3 21.4": ["bela"], "7.9 5.0 7.0": ["pract"], "28.4 21.7 23.9": ["multiton"], "8.6 -5.7 7.6": ["tled"], "12.8 6.5 7.9": ["anesthetised"], "9.5 21.4 -3.5": ["synarchist"], "-4.7 10.0 -1.3": ["mestic"], "8.0 17.4 10.2": ["shitted"], "-0.6 7.1 9.7": ["leaplings"], "7.2 -4.6 -6.1": ["affilliated"], "5.4 9.8 14.9": ["newsday"], "7.9 6.3 15.8": ["holloway"], "-2.7 5.5 7.1": ["caravanserais"], "22.7 -6.0 15.3": ["liquidized"], "-0.9 5.9 4.4": ["numerus"], "-9.3 7.2 -4.2": ["dars"], "5.7 4.9 11.3": ["scintillates"], "7.5 -5.1 24.3": ["platos"], "-6.6 -5.9 2.6": ["detemir"], "-1.7 -1.2 -6.6": ["hollywooddiv"], "5.1 21.9 15.6": ["ammi"], "-0.6 12.1 5.3": ["gematria"], "-5.6 11.7 4.7": ["rearresting"], "4.7 -5.9 5.8": ["thef"], "8.0 41.5 3.6": ["tyrrany"], "8.7 22.8 13.0": ["dischord"], "7.3 7.7 6.8": ["untaxing"], "-5.8 6.4 6.6": ["hypercoagulable"], "4.5 22.9 9.9": ["mythologizes"], "24.5 15.5 6.9": ["hammerblow"], "15.7 8.5 6.2": ["creaser"], "3.4 9.5 15.7": ["kere"], "8.2 6.8 7.7": ["rightto"], "-1.3 12.1 3.6": ["incoherencies"], "13.4 5.2 15.7": ["caballo"], "5.7 16.3 9.6": ["mostimportant"], "-0.3 1.8 12.6": ["thecenter"], "14.1 15.3 18.0": ["unridable"], "8.9 0.8 11.6": ["valle"], "3.0 0.5 5.1": ["disques"], "-0.2 13.8 3.8": ["veridical"], "7.4 28.5 4.0": ["weaponries"], "17.8 11.8 15.7": ["likker"], "16.3 3.2 15.9": ["deres"], "14.6 6.4 1.0": ["serviceprovider"], "9.4 6.2 20.7": ["noseriding"], "17.3 15.5 16.9": ["squinched"], "5.7 5.9 1.9": ["athetic"], "9.3 14.3 6.4": ["desertscape"], "2.4 1.6 -0.2": ["corder"], "5.1 6.8 24.4": ["sali"], "0.7 -5.5 2.4": ["multiservices"], "6.4 15.0 8.5": ["palava"], "9.2 9.9 6.6": ["trivium"], "-0.3 -2.2 5.8": ["antiscalants"], "3.6 12.8 16.9": ["happe"], "1.3 8.3 9.9": ["securiy"], "1.6 24.8 -3.0": ["rmy"], "1.8 8.6 15.4": ["overpumped"], "10.0 6.1 21.1": ["banta"], "-0.6 6.9 3.8": ["standarized"], "4.7 17.1 10.7": ["interecepted"], "-1.3 8.6 8.1": ["galiximab"], "-1.2 0.2 11.5": ["aveage"], "13.3 13.4 17.3": ["busto"], "-1.0 12.6 16.2": ["anergy"], "3.8 16.0 12.2": ["disputant"], "7.0 -0.3 7.9": ["schillings"], "2.0 30.1 5.6": ["postinvasion"], "2.4 11.6 7.1": ["varun"], "19.6 3.6 23.3": ["foof"], "1.5 15.3 2.3": ["moddable"], "12.3 9.4 5.4": ["camphone"], "1.8 3.8 7.4": ["mnutes"], "4.8 15.0 8.5": ["phagocyte"], "-0.4 13.9 6.5": ["blogmaster"], "5.5 2.6 4.5": ["demanda"], "7.1 19.3 5.0": ["bann"], "9.4 1.5 9.2": ["growt"], "12.5 2.7 3.2": ["mainframers"], "15.3 11.4 9.5": ["microcircuitry"], "18.4 -1.2 4.3": ["backruptcy"], "26.6 12.1 32.8": ["hawsers"], "-6.5 18.2 0.6": ["borde"], "17.7 12.9 5.3": ["oput"], "0.6 4.2 16.9": ["friedman"], "13.7 5.7 4.6": ["suffusion"], "1.8 1.8 10.8": ["triplexer"], "8.9 9.4 15.2": ["spocks"], "10.9 19.7 7.0": ["tasker"], "-1.8 6.2 3.0": ["picturising"], "3.2 -4.4 6.4": ["ambas"], "18.9 21.7 8.1": ["watergun"], "9.8 21.9 20.7": ["crumbers"], "8.2 2.7 7.1": ["hydrogenases"], "2.0 12.8 20.6": ["vascularised"], "5.4 6.2 17.6": ["ahna"], "5.9 12.8 12.3": ["pasmalltown"], "10.1 -2.1 14.3": ["uarter"], "0.1 -0.1 3.5": ["mantiene"], "-3.0 14.7 11.2": ["afamily"], "0.5 11.9 11.0": ["catchless"], "1.2 8.2 3.8": ["sealability"], "10.0 -1.0 -1.2": ["linepipe"], "13.7 15.7 8.9": ["gigant"], "4.2 4.3 10.0": ["hfs"], "-0.9 10.6 12.3": ["huna"], "1.2 14.6 3.9": ["postcolonialism"], "-0.1 9.5 -1.4": ["regiona"], "0.5 11.4 9.7": ["dometic"], "8.4 17.8 11.9": ["dirtballs"], "13.8 -1.3 2.2": ["ecostore"], "2.3 29.0 7.5": ["consequentialism"], "11.7 -3.3 5.9": ["petajoule"], "-0.1 9.3 12.8": ["preformances"], "-0.1 2.3 4.3": ["faites"], "-0.6 -1.7 3.9": ["thermoformable"], "9.1 7.3 13.1": ["pennyworth"], "2.6 -4.6 10.0": ["lhakhangs"], "3.5 8.3 18.2": ["fama"], "-1.1 8.5 10.1": ["yako"], "11.6 3.0 13.3": ["microbially"], "5.8 4.1 14.9": ["dulha"], "1.4 2.8 3.9": ["biomagnetic"], "3.5 1.5 8.9": ["naphthenic"], "9.1 27.2 11.7": ["reactionism"], "9.0 18.4 11.2": ["mechanizations"], "13.8 11.4 26.5": ["bedstraw"], "3.8 2.9 4.8": ["unborrowed"], "8.6 9.0 23.4": ["proteosome"], "5.3 -1.8 16.2": ["pickler"], "-0.5 19.9 9.5": ["exremely"], "3.5 12.1 13.3": ["costochondritis"], "6.4 -2.5 13.6": ["morton"], "7.0 19.3 8.0": ["militaires"], "13.0 9.8 36.6": ["panful"], "10.4 6.6 12.6": ["demic"], "19.3 11.6 24.8": ["grampy"], "0.3 10.0 8.5": ["reoccurance"], "6.2 9.4 0.3": ["denominates"], "21.3 15.8 31.1": ["adz"], "1.7 23.7 15.6": ["morns"], "13.3 17.4 29.3": ["headpin"], "8.0 10.9 4.6": ["gamebook"], "7.4 9.0 26.1": ["kadhai"], "8.8 10.8 6.7": ["bestsellerdom"], "-10.3 -3.4 0.7": ["lare"], "8.6 10.0 12.5": ["midteen"], "-0.1 5.6 11.6": ["sftp"], "2.4 25.3 8.8": ["codebooks"], "6.2 -10.8 -2.6": ["toopen"], "8.8 9.6 18.5": ["oocyst"], "3.8 22.3 12.1": ["atlast"], "9.2 0.3 8.1": ["poner"], "13.5 10.2 18.4": ["cruiseliners"], "22.0 30.0 16.0": ["valkyries"], "7.1 5.2 21.3": ["growhouse"], "22.8 9.4 8.8": ["grippable"], "12.9 8.3 24.0": ["turistas"], "5.5 1.3 -0.5": ["outplace"], "1.2 14.1 17.2": ["taraf"], "4.9 23.0 13.6": ["directedness"], "15.9 8.2 2.0": ["cropdusting"], "-1.0 -0.9 2.3": ["janajatis"], "1.3 -1.8 -4.3": ["perfromed"], "5.5 0.3 -0.3": ["amaxa"], "-2.8 1.8 13.2": ["khariff"], "5.6 5.8 6.3": ["deur"], "11.8 13.5 20.6": ["snowblow"], "9.6 18.4 12.6": ["originary"], "-2.0 3.3 7.1": ["paraneoplastic"], "10.0 9.7 10.1": ["hardstyle"], "21.7 7.3 31.2": ["alaia"], "10.1 9.7 26.5": ["chiffchaff"], "6.1 5.4 1.0": ["fabulis"], "11.5 22.2 6.1": ["inefficacious"], "-2.4 7.1 1.4": ["masterservant"], "12.2 -8.1 6.4": ["collecter"], "5.4 2.7 16.5": ["cesar"], "3.9 4.0 17.0": ["hyaluronate"], "-5.6 -2.2 5.3": ["ihl"], "13.1 12.1 9.8": ["seignorage", "environmentalresearchweb"], "10.9 13.3 9.6": ["lanscape"], "7.1 10.3 11.4": ["sulci"], "4.9 7.9 9.2": ["hostelers"], "13.7 11.2 18.3": ["feaces"], "5.1 18.8 13.1": ["contrario"], "2.2 8.3 9.9": ["waale"], "8.7 9.6 5.1": ["lente"], "11.8 23.6 5.6": ["promiser"], "8.9 13.2 4.1": ["phyical"], "-1.9 17.5 6.4": ["bootstrapper"], "2.0 -6.0 0.8": ["inrevium"], "6.9 6.5 -0.7": ["vernment"], "4.0 -1.8 6.6": ["bls"], "11.1 7.3 15.2": ["sirignanos"], "-4.3 23.1 2.7": ["debilitations"], "0.3 -1.0 10.1": ["enologists"], "7.2 15.8 9.5": ["superflous"], "7.6 2.2 37.6": ["calamares"], "2.7 10.0 5.0": ["saythat"], "-7.0 7.8 5.0": ["effec"], "11.4 10.6 3.0": ["triplewide"], "-7.3 0.7 -0.4": ["pation"], "3.3 1.2 9.7": ["apostille"], "15.4 10.2 5.7": ["chanels"], "-5.4 0.9 9.4": ["oesophagitis"], "-3.7 7.5 3.9": ["neurosteroids"], "14.6 18.1 15.4": ["sholder"], "2.3 13.5 7.7": ["blatt"], "13.8 13.3 15.9": ["ondol"], "11.5 -6.6 2.0": ["resoultion"], "11.6 23.2 19.8": ["unhallowed"], "13.1 6.4 9.8": ["chunck"], "11.7 5.1 12.1": ["zapatos"], "15.0 19.1 11.3": ["tactilely"], "21.2 13.2 19.2": ["photosynthesising"], "-4.9 -1.2 22.1": ["chapa"], "1.2 15.4 9.6": ["nevr"], "-2.7 4.6 9.7": ["daylife"], "8.9 17.4 6.1": ["dimensionalize"], "1.2 19.1 18.1": ["somehwat"], "2.1 16.0 2.3": ["wazir"], "8.2 5.9 12.7": ["stdout"], "3.1 8.9 9.5": ["spirted"], "22.9 6.0 20.8": ["creosoted"], "6.6 9.6 17.1": ["unconsecrated"], "8.0 24.3 16.2": ["ingenuities"], "8.9 4.0 6.5": ["torchiere"], "25.9 8.5 19.5": ["vespa"], "10.0 19.5 3.0": ["sovereignly"], "13.8 12.7 14.3": ["superstrain"], "9.4 2.3 1.3": ["pushmail"], "9.9 2.0 -0.2": ["compatibile"], "2.2 -1.8 6.8": ["pread"], "-3.2 8.1 6.4": ["reinterventions"], "8.0 3.9 28.7": ["croque"], "4.0 11.4 3.0": ["yake"], "13.9 6.3 14.5": ["looseners"], "-0.3 23.2 0.5": ["monad"], "9.5 -2.6 7.3": ["payfor"], "10.3 3.5 29.8": ["grana"], "2.2 13.8 9.7": ["aftewards"], "7.6 18.4 1.9": ["prophesising"], "18.5 24.0 26.8": ["seadogs"], "19.0 10.5 11.6": ["deformers"], "14.0 20.7 15.7": ["spelunk"], "2.4 21.3 4.8": ["disutility"], "7.9 10.9 23.6": ["wots"], "2.3 8.9 7.0": ["beamsplitters"], "-5.0 -4.5 -3.8": ["studetns"], "-0.5 0.8 -0.7": ["regualtion"], "9.1 6.7 11.0": ["meena"], "-3.0 10.8 9.3": ["outtages"], "2.8 2.7 10.5": ["elds"], "-1.8 13.1 19.1": ["orthorexics"], "8.0 9.5 7.2": ["jvm"], "5.9 16.5 8.9": ["attaque"], "-2.2 16.8 2.8": ["equanimous"], "11.7 11.5 2.2": ["bwired"], "7.9 3.9 6.2": ["onwer"], "7.7 -1.2 18.2": ["esti"], "2.9 19.8 1.9": ["transformatory"], "5.7 2.3 23.6": ["nonmatching"], "11.2 6.7 15.2": ["indierock"], "10.4 -1.3 7.8": ["modaraba"], "1.0 8.9 11.4": ["cavatina"], "21.5 25.7 16.3": ["halflings"], "7.6 3.9 22.2": ["werth"], "8.7 1.7 7.9": ["syenitic"], "18.1 -2.3 12.8": ["pipelayer"], "13.4 22.2 10.7": ["happeneing"], "22.3 -10.2 3.7": ["producted"], "4.0 -1.6 16.8": ["newid"], "7.9 9.1 25.0": ["multiflora"], "4.3 1.3 15.4": ["daywork"], "3.2 13.8 5.8": ["abasing"], "0.4 13.3 -2.2": ["oving"], "3.9 17.8 7.6": ["laos"], "-9.7 8.9 7.6": ["parasitological"], "18.2 5.1 8.0": ["megastructures"], "6.4 7.7 5.5": ["nohitter"], "3.2 14.9 15.6": ["swansongs"], "7.2 13.3 19.7": ["ggg"], "6.5 23.0 8.2": ["nowness"], "7.5 32.2 -0.1": ["innnocent"], "7.3 21.1 19.0": ["birdbrained"], "13.1 13.2 13.1": ["tawdriest"], "14.8 38.4 6.5": ["infowar"], "2.5 11.9 10.8": ["familylike"], "15.2 8.2 17.2": ["timberwork"], "6.0 6.2 23.5": ["mista"], "17.0 7.0 9.5": ["wayleave"], "5.6 22.6 7.6": ["thepolitical"], "-6.7 -1.0 9.4": ["depsipeptide"], "4.3 9.4 12.6": ["sterndrives"], "8.4 22.5 12.8": ["putterhead"], "14.9 -3.1 -5.1": ["coutesy"], "5.5 -5.6 -5.6": ["rectorship"], "13.0 0.9 14.5": ["tetrapak"], "23.2 0.1 21.8": ["spiegeltent"], "2.5 1.4 4.9": ["llamada"], "4.0 10.2 3.3": ["indefintely"], "10.5 18.7 10.2": ["aplace"], "2.7 6.0 11.5": ["dispositioning"], "7.2 6.1 7.2": ["bota"], "2.1 11.7 -0.4": ["icu"], "11.6 -5.4 4.4": ["onderzoek"], "6.7 4.6 2.3": ["megapascals"], "6.1 11.5 9.3": ["uhmmm"], "1.5 2.2 16.4": ["mcc"], "12.4 -9.1 -0.2": ["inludes"], "16.6 2.5 11.8": ["decalitres"], "0.3 16.2 10.8": ["intrafamilial"], "3.6 -2.9 10.6": ["consturction"], "6.6 5.3 -0.5": ["offinancial"], "18.0 8.2 23.6": ["spooner"], "7.1 -4.6 4.4": ["calcipotriol"], "3.8 17.5 19.2": ["liftover"], "10.5 24.8 12.1": ["drivelling"], "7.1 13.7 9.8": ["gellin"], "13.6 28.8 8.0": ["vidcam"], "7.7 4.8 14.3": ["praat"], "6.6 -1.1 1.9": ["sulfonated"], "8.3 14.5 17.9": ["trichomonosis"], "13.2 -6.9 14.4": ["menthe"], "-2.0 -3.7 3.5": ["thinkdesign"], "4.6 21.8 0.4": ["formenting"], "1.8 14.2 12.3": ["gunda"], "-1.2 8.6 11.0": ["serologically"], "1.0 -2.7 -3.7": ["willreceive"], "18.3 -1.6 11.7": ["bouzoukis"], "14.7 6.4 25.0": ["alstromeria"], "21.4 6.3 3.2": ["bloggerati"], "4.9 3.7 5.9": ["outearned"], "9.6 1.1 13.6": ["ahing"], "13.9 23.9 13.2": ["gorily"], "13.4 9.1 13.6": ["mantillas"], "4.0 6.5 -4.2": ["fuelcell"], "1.7 8.0 9.0": ["mitogen"], "6.8 12.1 4.8": ["quer"], "2.1 9.1 3.5": ["wanda"], "-5.1 3.4 15.6": ["kasal"], "5.0 15.3 12.4": ["preist"], "1.5 7.3 9.3": ["hoffman"], "-7.3 8.2 13.6": ["permittable"], "2.5 -6.9 9.4": ["inititated"], "18.0 29.0 10.7": ["splode"], "0.4 7.7 13.5": ["limbal"], "4.8 8.9 7.2": ["nonoperated"], "-0.1 9.2 12.8": ["saponification"], "7.0 17.3 8.8": ["firestops"], "18.1 9.9 6.2": ["playard"], "0.3 3.3 7.9": ["netfilter"], "0.4 18.8 14.5": ["dispensability"], "7.4 8.4 10.6": ["flomax"], "10.7 17.8 1.0": ["breachers"], "-4.7 19.7 3.5": ["hesed"], "13.3 9.6 16.5": ["andeven"], "1.6 2.8 3.4": ["bookfairs"], "7.1 19.0 2.2": ["slimebag"], "3.9 9.7 3.9": ["hmmmmmmm"], "-1.4 18.1 5.2": ["womanized"], "11.6 4.3 12.1": ["kwhs"], "5.6 11.0 8.1": ["mineralogically"], "8.0 17.7 12.2": ["favorate"], "3.5 15.0 11.5": ["cutmen"], "9.5 6.2 30.4": ["butteriness"], "-3.1 1.7 8.5": ["majorityof"], "-4.6 -1.8 6.6": ["premenopause"], "1.5 22.8 18.7": ["meanin"], "2.8 18.5 11.3": ["carnap"], "14.5 11.4 27.8": ["decoctions"], "7.5 4.9 1.8": ["andthree"], "10.7 3.1 4.7": ["discoved"], "21.1 7.1 12.5": ["octenol"], "5.4 21.9 11.9": ["youknow"], "8.4 10.5 11.2": ["albitized"], "11.5 10.9 6.6": ["funktastic"], "16.5 9.5 6.9": ["mkay"], "16.2 14.6 4.5": ["arean"], "11.6 6.1 11.3": ["crudeoil"], "3.1 7.7 1.6": ["socia"], "2.2 -2.4 13.7": ["puroks"], "1.2 5.9 -1.1": ["searc"], "11.8 17.7 33.3": ["saltless"], "1.4 12.3 4.5": ["quaternion"], "11.0 10.8 1.1": ["jeapordise"], "15.6 12.0 28.4": ["manjha"], "12.5 10.6 24.1": ["schistosomes"], "19.4 30.2 18.5": ["scrunt"], "0.4 -13.9 -3.1": ["pital"], "-0.9 6.5 3.3": ["offficers"], "13.6 6.3 6.0": ["yeasterday"], "9.5 3.7 7.0": ["arragements"], "-0.8 3.6 2.7": ["antifolates"], "22.6 8.6 28.3": ["lacewing"], "7.7 19.0 6.0": ["abjectness"], "3.4 7.1 12.9": ["alexa"], "5.8 -3.7 19.1": ["recork"], "-1.0 11.5 3.7": ["itas"], "15.5 17.6 4.6": ["malfeasants"], "8.0 14.1 12.9": ["insentive"], "5.0 0.8 4.0": ["amnd"], "10.3 3.6 28.7": ["romanesco"], "7.3 -1.9 2.7": ["myplace"], "8.1 9.2 24.0": ["straightish"], "-1.6 -3.2 0.1": ["screeing"], "4.1 13.8 14.7": ["shorthead"], "4.2 2.4 17.8": ["doktor"], "-1.3 -3.0 15.7": ["sinabing"], "25.9 10.8 10.0": ["awhirl"], "1.7 12.7 8.2": ["thirddegree"], "17.8 20.5 33.0": ["spatterdock"], "17.0 6.8 11.7": ["machin"], "7.2 14.2 2.9": ["asone"], "1.8 10.5 2.5": ["uscitizen"], "4.2 13.7 9.7": ["kagan"], "7.3 -0.8 7.9": ["primeros"], "4.6 22.7 9.9": ["enervates"], "7.9 7.3 11.9": ["necesario"], "-2.2 9.1 9.0": ["elena"], "-0.4 -1.4 -4.7": ["gaurantees"], "6.9 2.6 11.2": ["urbanwear"], "-5.0 3.5 6.0": ["trustys"], "16.8 11.3 19.5": ["scroungy"], "8.5 6.2 20.1": ["towkay"], "13.2 10.1 -2.8": ["superclean"], "-0.9 17.9 4.8": ["desensitises"], "-0.4 6.0 -7.0": ["cheerleaded"], "15.4 6.1 1.5": ["announcemnt"], "10.2 1.4 5.7": ["echocardiograph"], "16.3 10.7 34.1": ["unfried"], "1.1 4.4 8.4": ["trimethyl"], "12.0 13.3 15.5": ["dorsally"], "1.4 7.5 19.7": ["poya"], "2.5 5.8 0.9": ["nonexposed"], "17.9 0.9 17.0": ["elmo"], "6.9 13.1 15.8": ["midback"], "22.0 14.4 11.9": ["permabulls"], "12.0 15.1 10.4": ["hateration"], "10.2 12.3 19.3": ["manboobs"], "10.0 10.4 23.8": ["goma"], "1.2 3.0 5.8": ["akinesia"], "-6.9 -1.4 31.4": ["bayman"], "-8.3 -5.8 9.9": ["collegebound"], "13.6 0.9 10.3": ["decare"], "-10.1 3.2 2.2": ["igovt"], "10.5 2.0 -0.1": ["listy"], "13.7 21.4 6.8": ["homecrowd"], "3.6 10.0 9.0": ["anke"], "6.0 15.3 12.9": ["regionalisms"], "8.2 10.9 5.6": ["straght"], "4.5 2.3 15.4": ["buro"], "13.6 5.6 12.0": ["coner"], "19.8 15.6 13.3": ["candlelights"], "14.3 12.8 17.1": ["wisnae"], "7.6 9.6 13.0": ["yeux"], "12.4 12.9 16.3": ["jenever"], "2.8 7.8 5.2": ["ored"], "8.3 15.3 5.4": ["comit"], "4.4 6.6 15.0": ["krausening"], "8.7 4.6 7.4": ["contenu"], "14.0 11.0 21.8": ["seedbank"], "18.4 22.6 23.4": ["sastrugi"], "3.5 8.1 12.6": ["alef"], "11.7 15.3 6.1": ["ironsmith"], "-1.0 5.4 -4.1": ["uccess"], "8.2 -3.0 7.9": ["konpa"], "2.9 2.2 9.2": ["volunters"], "9.8 19.2 10.5": ["drillfield"], "8.4 1.3 4.4": ["dyne"], "16.0 2.5 28.8": ["tomate"], "-1.5 13.9 21.4": ["unsa"], "0.3 -3.2 1.7": ["nonminorities"], "-3.4 9.3 5.5": ["misusage"], "10.0 15.7 1.1": ["saleswise"], "9.8 15.3 15.4": ["blastbeats"], "18.1 18.9 12.8": ["joneses"], "11.2 -1.5 1.4": ["acounting"], "2.3 31.4 13.5": ["npc"], "3.1 2.6 4.9": ["wakeskates"], "5.4 6.9 -0.0": ["tracklistings"], "8.4 9.8 8.7": ["mechitzah"], "11.1 25.9 -1.6": ["abhored"], "8.8 2.3 -3.4": ["heise"], "-2.8 28.4 0.9": ["messianists"], "11.2 22.8 16.8": ["abideth"], "4.1 16.3 12.9": ["versifying"], "12.4 7.0 2.5": ["wheelchaired"], "0.9 6.6 3.2": ["garh"], "1.2 11.0 11.0": ["meck"], "18.0 12.8 13.0": ["overspills"], "0.6 10.3 8.6": ["cameoing"], "3.9 -2.7 7.8": ["insieme"], "10.2 -2.3 7.3": ["arnings"], "13.1 10.7 22.2": ["fooler"], "-5.4 1.8 6.4": ["challen"], "15.1 7.4 31.3": ["pigout"], "14.4 15.4 12.5": ["strees"], "3.3 0.5 0.1": ["rov"], "21.3 12.1 41.7": ["dragonfish"], "8.7 17.3 3.5": ["puritanically"], "6.5 7.4 10.0": ["plent"], "18.5 8.8 26.2": ["botfly"], "9.8 -1.0 11.7": ["totebag"], "5.1 0.8 15.4": ["verano"], "5.4 -3.9 10.7": ["cac"], "11.3 12.6 13.7": ["geckel"], "15.6 17.1 16.9": ["nuttery"], "5.2 3.3 16.2": ["microfossil"], "0.8 -8.8 1.9": ["opm"], "18.2 -1.1 15.8": ["bechmark"], "8.9 16.4 11.4": ["addles"], "17.6 -3.1 22.6": ["kfc"], "3.1 -1.2 -7.8": ["servis"], "12.0 19.1 31.2": ["bulbils"], "4.3 11.9 4.2": ["interpellated"], "7.3 13.3 12.6": ["aybe"], "6.3 14.0 11.9": ["depleated"], "13.4 22.1 7.9": ["trepid"], "12.0 4.8 18.5": ["titian"], "9.5 11.9 20.5": ["basketfuls"], "4.0 5.4 14.2": ["gupshup"], "3.9 7.6 3.5": ["unicef"], "4.1 7.9 5.2": ["dng"], "-5.3 2.3 11.9": ["aay"], "-0.3 -8.3 6.0": ["truh"], "2.5 3.3 -0.6": ["empleados"], "8.2 16.3 7.7": ["activatable"], "4.3 11.6 10.0": ["rahs"], "0.9 11.8 6.1": ["inda"], "-0.8 5.8 -1.7": ["cting"], "-4.4 23.6 -5.5": ["abetters"], "5.3 9.7 7.4": ["unconjugated"], "2.1 -1.4 5.7": ["subracks"], "5.1 -0.0 6.5": ["upfrom"], "12.7 23.1 12.0": ["arete"], "3.6 10.2 12.0": ["slamfest"], "0.7 20.5 -0.4": ["pseudonymity"], "4.0 9.2 12.3": ["dugo"], "14.3 21.4 1.4": ["realisitic"], "17.6 5.1 15.8": ["inkstand"], "16.3 4.5 15.5": ["millionares"], "4.8 2.8 8.4": ["cerebrospinal"], "1.5 10.9 5.8": ["perfuse"], "3.2 6.2 1.9": ["hypointense"], "9.4 1.3 0.5": ["immunohematology"], "19.6 3.7 10.4": ["compnaies"], "22.2 16.2 24.2": ["dremel"], "0.3 7.5 13.7": ["eachway"], "6.4 10.8 15.0": ["twominute"], "-1.6 4.5 4.3": ["categorie"], "13.3 8.3 10.8": ["bordo"], "15.9 12.7 25.0": ["zelkova"], "18.9 6.0 5.9": ["remerchandise"], "4.6 11.8 17.9": ["goldberg"], "4.9 6.0 14.7": ["biomathematics"], "17.2 9.3 26.2": ["mielies"], "5.9 5.4 11.0": ["multifidus"], "13.0 4.1 12.6": ["shil"], "-1.6 21.5 8.9": ["behalfs"], "12.2 7.0 17.6": ["milles"], "0.6 -5.1 11.0": ["hydroslide"], "2.6 6.1 1.4": ["wasent"], "9.6 -0.3 30.2": ["restauarant"], "16.1 22.6 15.6": ["schlemiels"], "11.2 9.8 15.2": ["ainda"], "7.4 19.8 9.6": ["utterer"], "8.6 7.6 8.3": ["birefringent"], "4.4 13.0 16.7": ["zor"], "20.4 20.9 19.6": ["prybar"], "15.3 25.4 24.1": ["disgustingness"], "6.0 18.2 5.0": ["bootsteps"], "0.1 10.1 2.0": ["diappointed"], "7.2 17.6 3.6": ["fraternite"], "2.1 11.3 4.2": ["beamwidth"], "7.4 0.1 2.8": ["opertions"], "0.6 5.2 13.6": ["jatara"], "4.6 5.6 12.6": ["homeowers"], "17.7 5.9 8.6": ["clops"], "-3.4 -2.8 1.2": ["subcommitte"], "4.3 13.9 6.6": ["wingwalking"], "-1.3 4.0 13.3": ["caffeination"], "3.5 22.1 11.6": ["aproblem"], "1.3 9.8 10.5": ["sewerlines"], "16.8 17.9 13.8": ["mumblers"], "17.8 25.8 -5.6": ["biowar"], "7.2 8.1 -2.7": ["openeing"], "7.0 14.9 5.3": ["burquas"], "21.1 -3.2 16.4": ["dishwash"], "8.7 2.7 10.0": ["tranplant"], "1.5 18.2 1.1": ["empathizers"], "0.9 1.6 4.0": ["kpaul"], "1.0 4.5 3.7": ["underlift"], "3.2 8.7 2.5": ["hailer"], "14.6 17.4 16.1": ["diamagnetic"], "1.4 12.4 3.4": ["magnitute"], "-4.0 6.3 -2.2": ["ooks"], "14.0 6.8 5.6": ["suppled"], "4.4 0.8 4.4": ["reinclusion"], "4.8 -2.2 -5.7": ["cabinent"], "14.6 12.3 29.9": ["gestates"], "5.1 13.4 13.5": ["randon"], "1.1 6.4 13.0": ["kole"], "10.1 22.1 -4.0": ["destructs"], "14.1 13.9 3.7": ["hypers"], "-0.6 1.8 7.6": ["assement"], "2.0 15.1 6.9": ["pq"], "14.9 19.3 16.5": ["toxified"], "13.4 12.1 7.7": ["confecting"], "3.8 27.4 4.4": ["egoic"], "6.6 13.8 15.7": ["lorem"], "11.8 -0.0 8.6": ["offmarket"], "3.3 12.8 10.5": ["weeky"], "4.3 7.8 6.3": ["quinoline"], "10.2 21.8 12.6": ["footba"], "10.7 1.8 20.7": ["grazings"], "10.9 12.6 18.3": ["snowbrush"], "8.1 5.5 0.7": ["copywrited"], "-2.9 15.9 14.2": ["tounderstand"], "-3.0 1.5 11.1": ["linolenic"], "7.1 11.1 12.4": ["juliet"], "12.2 2.7 20.1": ["tobogganers"], "7.8 15.1 18.3": ["overfertilizing"], "14.3 10.8 18.2": ["jackknives"], "17.1 7.6 16.0": ["oilservice"], "20.1 10.6 24.5": ["oviraptors"], "7.8 20.0 2.7": ["disparagers"], "-2.5 19.6 -0.4": ["digusted"], "6.5 1.0 8.5": ["nottingham"], "22.8 11.9 19.5": ["tittie"], "15.2 5.7 16.5": ["divin"], "16.2 9.5 10.7": ["avariciously"], "4.8 6.0 8.2": ["feul"], "-6.1 3.6 3.7": ["ilness"], "5.3 14.8 23.9": ["vegeterian"], "-2.5 11.5 4.6": ["canonist"], "-0.3 10.6 0.9": ["respectibility"], "11.8 10.1 16.0": ["timesthree"], "16.4 6.9 19.2": ["tradionally"], "-0.9 15.3 0.5": ["importantance"], "8.3 7.6 5.7": ["synchroniser"], "13.7 16.2 4.1": ["conceiveable"], "2.8 20.4 19.2": ["alphavirus"], "18.3 8.1 32.2": ["sammiches"], "1.3 21.8 -2.6": ["uncomforting"], "14.1 3.7 32.8": ["corncakes"], "7.6 -6.3 -1.7": ["bilastine"], "11.9 7.9 18.9": ["holday"], "9.6 1.3 -0.2": ["viscom"], "0.1 1.5 -8.5": ["neweurasia"], "7.9 -3.2 10.5": ["gweld"], "8.5 6.8 -0.9": ["trifurcate"], "20.2 5.2 20.8": ["burlwood"], "5.1 12.2 11.5": ["metus"], "14.5 5.3 36.8": ["etoufee"], "-6.1 8.6 9.8": ["beguine"], "16.3 32.2 8.7": ["destructable"], "-0.2 14.7 -3.4": ["exculpates"], "0.0 23.9 13.1": ["irreplaceably"], "7.7 13.4 15.9": ["saala"], "6.6 13.6 1.1": ["pravda"], "1.0 6.5 -0.6": ["propo"], "15.1 16.2 16.9": ["unlatches"], "9.4 -4.0 5.8": ["annunced"], "-2.2 0.5 15.2": ["palaeoclimate"], "8.1 14.2 11.7": ["programatically"], "7.7 19.3 9.0": ["schmozzle"], "9.9 10.4 8.7": ["doubleclicking"], "9.4 6.7 13.1": ["hagwons"], "12.4 21.9 0.6": ["snoopware"], "6.7 13.1 -1.5": ["sercurity"], "-8.9 3.2 12.3": ["multivessel"], "-0.3 4.6 15.2": ["ntil"], "-2.6 -4.0 -8.3": ["acoording"], "18.5 13.9 13.3": ["letterings"], "4.2 -2.5 3.6": ["netsales"], "4.5 6.6 20.3": ["phal"], "11.0 4.0 -2.2": ["governm"], "2.9 18.9 2.5": ["feminicide"], "14.1 10.3 28.2": ["splendens"], "-2.5 5.6 6.9": ["nanochemistry"], "10.2 10.0 31.0": ["sulfurs"], "7.0 11.0 19.0": ["alongthe"], "8.0 12.0 6.9": ["threa"], "10.4 16.3 11.2": ["superoxides"], "6.1 9.7 4.0": ["unpunctuality"], "9.4 19.3 16.7": ["mistiness"], "12.6 6.1 20.3": ["cueca"], "9.4 5.9 13.5": ["canvased"], "8.0 10.7 12.4": ["rushhour"], "7.3 0.1 13.7": ["cinque"], "5.4 5.0 9.5": ["wonderstrike"], "0.6 6.8 4.6": ["twopoint"], "-9.6 -0.6 -4.5": ["statemented"], "-2.0 -3.2 4.8": ["neonatalogist"], "3.8 9.3 7.6": ["adscam"], "9.6 11.9 10.5": ["muleteers"], "7.3 14.9 3.8": ["subcamps"], "-8.9 -4.3 10.7": ["munici"], "-2.4 8.4 6.5": ["glaucomatous"], "15.4 18.8 6.0": ["betokening"], "14.3 21.2 14.8": ["minuteness"], "23.5 10.4 10.4": ["mamoth"], "-2.7 10.8 4.1": ["alcholism"], "-1.2 11.0 8.4": ["sleeptime"], "6.5 1.7 6.6": ["lessions"], "4.6 4.7 -2.3": ["livescan"], "0.1 -2.1 8.6": ["reorchestrated"], "19.6 12.4 21.4": ["karabiner"], "5.4 5.3 9.4": ["frumpier"], "13.2 26.1 18.6": ["shunners"], "4.9 10.0 11.7": ["offcutter"], "21.9 12.9 24.2": ["situp"], "10.2 2.3 3.9": ["hotelling"], "15.3 6.4 35.6": ["fishboat"], "-0.5 9.9 8.8": ["begininng"], "11.7 21.2 10.6": ["rhythmn"], "2.8 10.2 16.4": ["adsorbate"], "-2.2 8.4 1.8": ["appropriative"], "15.5 5.3 28.5": ["manx"], "1.1 15.6 -0.6": ["needfor"], "14.5 2.1 26.0": ["chitarra"], "6.1 5.8 8.4": ["negli"], "8.2 1.8 13.0": ["sinon"], "-4.5 7.9 8.0": ["absorbability"], "2.9 0.2 11.8": ["nair"], "10.0 11.0 9.8": ["minimovie"], "14.1 5.1 41.6": ["cepes"], "12.5 19.1 17.7": ["craneway"], "4.3 19.5 8.6": ["upteenth"], "5.0 2.7 8.5": ["escribir"], "2.2 3.1 2.0": ["multiparametric"], "12.8 9.9 33.5": ["brachiopod"], "6.3 22.7 2.2": ["unairworthy"], "4.1 13.4 5.5": ["miscalls"], "-1.8 6.3 5.5": ["niggunim"], "10.0 2.6 3.2": ["financi"], "12.8 4.5 36.1": ["cipollini"], "5.3 17.1 4.4": ["oter"], "8.9 1.1 16.0": ["jarana"], "10.4 5.7 9.1": ["eml"], "10.4 2.7 1.7": ["societe"], "24.2 7.6 32.0": ["stringybark"], "9.0 14.3 5.4": ["autoinjectors"], "-0.7 20.7 5.1": ["generalises"], "-1.7 11.7 7.9": ["chowkis"], "3.3 6.6 7.9": ["dirver"], "2.6 17.0 4.7": ["sooting"], "14.2 6.0 11.2": ["pitheads"], "8.6 11.5 11.7": ["homewreckers"], "11.3 -0.2 -0.7": ["assocations"], "7.3 7.4 12.8": ["libbers"], "6.2 20.4 13.7": ["hahahahahahaha"], "13.6 16.8 7.3": ["finallly"], "4.9 10.9 9.1": ["furanones"], "5.1 6.6 4.4": ["courriel"], "20.6 10.8 39.7": ["finback"], "14.6 4.9 14.7": ["fourwheeler"], "18.5 7.5 21.0": ["haywagon"], "0.3 10.7 10.7": ["anomymity"], "2.7 -1.7 17.1": ["kaw"], "8.9 12.6 14.9": ["ohhs"], "17.3 -0.2 15.5": ["bioanalytics"], "9.8 6.3 3.7": ["anciens"], "11.9 18.6 -0.6": ["inspirited"], "9.6 4.2 7.8": ["nanometal"], "3.0 8.6 2.4": ["hidalgo"], "11.6 16.7 13.4": ["paralell"], "6.7 -5.4 13.7": ["songfests"], "-1.3 -0.0 6.9": ["racemeeting"], "9.1 6.4 9.2": ["opne"], "5.3 15.7 7.2": ["deceaseds"], "-5.7 7.4 -1.1": ["startable"], "-1.6 4.3 9.8": ["sextons"], "10.7 3.8 27.7": ["grevilleas"], "-3.0 9.1 16.2": ["whanaungatanga"], "7.3 17.8 3.8": ["nondeterministic"], "-4.9 5.5 8.1": ["haplotyping"], "10.3 4.4 7.4": ["noncharitable"], "4.3 8.7 -2.9": ["availableto"], "15.1 7.6 29.4": ["phormium"], "-0.0 -3.0 4.5": ["dpt"], "1.6 12.3 5.5": ["mutch"], "11.1 -0.3 1.8": ["epilators"], "10.6 8.5 14.1": ["frugalistas"], "0.0 7.0 9.6": ["warranteed"], "19.2 17.1 25.4": ["abutilon"], "0.1 -6.8 4.4": ["etrak"], "4.6 11.5 5.6": ["forword"], "7.5 -3.6 2.8": ["preformulation"], "16.6 20.8 10.3": ["wost"], "-6.5 4.1 6.9": ["leiomyomas"], "6.0 10.7 20.1": ["doges"], "1.0 10.6 15.5": ["passthroughs"], "11.9 6.9 14.6": ["squeakier"], "9.7 1.4 17.6": ["cartilege"], "7.5 2.7 6.6": ["dpkg"], "4.2 3.0 13.9": ["overed"], "7.7 0.5 18.0": ["baga"], "9.8 20.6 5.0": ["basterd"], "0.4 10.0 5.2": ["mandat"], "5.9 8.7 9.6": ["rmetz"], "-5.3 2.7 2.1": ["physcian"], "16.4 29.6 24.6": ["triremes"], "18.8 14.7 33.4": ["conching"], "16.7 10.8 15.1": ["thistime"], "11.5 18.6 29.4": ["quackgrass"], "-2.7 7.3 7.2": ["cather"], "12.8 9.6 12.0": ["roseum"], "14.5 17.0 7.8": ["softw"], "6.0 8.0 8.7": ["momen"], "7.6 -3.0 16.2": ["asta"], "6.3 -5.9 12.1": ["miliwn"], "12.9 2.7 11.0": ["superheater"], "2.9 6.4 5.3": ["writng"], "20.0 21.0 23.6": ["sanguinea"], "24.5 13.3 16.3": ["puyo"], "3.9 -0.6 -3.1": ["asr"], "2.8 2.8 7.1": ["sals"], "0.4 12.3 12.6": ["hypervirulent"], "8.4 23.8 17.8": ["quiddity"], "4.6 15.8 1.6": ["persay"], "3.3 0.1 6.4": ["ducation"], "1.4 1.9 16.9": ["melinda"], "18.1 2.9 10.5": ["supershort"], "1.0 6.5 10.9": ["womp"], "7.3 6.8 8.2": ["superdrive"], "16.7 9.4 29.2": ["rootballs"], "-9.6 5.9 1.4": ["balsalazide"], "8.4 27.3 2.3": ["overcommunicate"], "-0.7 16.3 8.3": ["humorlessly"], "2.7 -6.0 10.4": ["broo"], "10.0 14.6 3.8": ["efcc"], "8.7 6.6 1.2": ["remixable"], "14.6 6.1 12.9": ["perforators"], "14.2 9.4 3.1": ["netlabel"], "1.0 12.2 28.9": ["ricelands"], "5.0 0.7 9.9": ["ferrotitanium"], "12.5 10.6 10.9": ["pottymouth"], "-7.1 1.7 0.4": ["wilayas"], "10.7 25.2 16.3": ["thuggy"], "20.6 1.6 10.6": ["handcrank"], "14.0 10.3 28.9": ["foram"], "11.7 17.6 14.5": ["abstemiousness"], "12.4 12.6 4.5": ["cameleers"], "13.2 5.7 19.0": ["bandera"], "0.3 1.9 4.5": ["distinquished"], "4.3 2.9 7.6": ["pregnacy"], "9.4 16.6 17.9": ["pontianak"], "0.5 16.1 9.1": ["committeepeople"], "6.3 21.3 8.7": ["messager"], "12.5 6.7 36.4": ["doughballs"], "6.9 10.7 1.9": ["datapaths"], "9.0 -1.5 4.1": ["gtslearning"], "3.3 6.7 3.6": ["noto"], "14.9 1.6 7.9": ["freespending"], "2.5 18.9 10.7": ["redknapp"], "15.3 11.9 19.7": ["slurper"], "7.1 -0.6 1.0": ["pga"], "9.8 7.6 17.3": ["lepidolite"], "-6.6 10.5 -3.8": ["recogition"], "8.4 -7.9 9.3": ["pharmacys"], "19.2 7.5 11.4": ["unscaled"], "-0.0 3.7 11.0": ["agisted"], "0.2 -4.8 14.1": ["haeng"], "-0.1 15.1 11.0": ["caucusers"], "1.7 16.6 -3.9": ["plagiarizer"], "4.1 18.8 18.7": ["preeti"], "9.4 8.0 6.1": ["cheul"], "9.5 15.9 6.1": ["fictionalisation"], "-0.6 6.0 10.7": ["contravida"], "3.5 19.3 9.8": ["commmon"], "2.4 19.3 13.5": ["nondesignated"], "-1.0 21.9 4.5": ["tzaddikim"], "11.8 9.0 14.8": ["resuced"], "-1.6 0.8 5.7": ["intinerary"], "3.0 10.7 10.6": ["backrider"], "-9.7 -0.3 -4.7": ["coordinater"], "1.1 14.2 4.6": ["companionships"], "11.9 5.1 9.6": ["hectar"], "-1.1 12.0 10.6": ["karoon"], "9.9 12.9 11.7": ["sdcard"], "14.4 17.4 13.8": ["vould"], "3.6 8.1 5.6": ["puedes"], "13.1 15.8 6.4": ["schemozzle"], "8.3 7.3 14.2": ["vestal"], "0.9 1.5 4.8": ["familiale"], "9.3 1.3 5.8": ["escuela"], "-1.2 5.7 4.8": ["insited"], "7.3 9.4 2.8": ["afaik"], "8.5 13.0 6.1": ["owuld"], "13.4 11.5 11.6": ["raiments"], "7.1 24.8 13.7": ["mwananchi"], "6.9 5.3 8.8": ["periodo"], "0.1 8.4 5.3": ["naveen"], "0.8 11.3 4.0": ["thetournament"], "3.1 14.4 11.8": ["berba"], "3.8 1.8 18.8": ["ekonomiya"], "-0.0 8.7 10.4": ["hout"], "-5.8 -2.7 -8.4": ["leagu"], "1.3 14.4 10.6": ["atttention"], "15.6 6.0 17.3": ["citrines"], "9.5 5.5 9.4": ["fraude"], "20.0 15.5 20.8": ["samisen"], "-0.6 13.4 16.1": ["spelldown"], "18.3 7.8 1.6": ["renna"], "4.1 1.4 4.3": ["mightbe"], "21.6 14.6 40.2": ["pacus"], "11.0 12.6 9.7": ["juddery"], "-3.4 11.1 9.9": ["lifestages"], "22.5 15.3 10.4": ["seamiest"], "10.0 15.3 5.6": ["pluckier"], "5.5 23.1 -0.3": ["shamefull"], "9.6 16.9 9.5": ["shtum"], "20.5 25.0 8.2": ["eeevil"], "-0.3 5.6 6.8": ["heterotaxy"], "7.0 17.3 16.3": ["overshop"], "5.7 8.0 1.2": ["cordonned"], "15.9 -4.8 4.5": ["masterplanner"], "2.3 14.4 4.2": ["hance"], "4.3 10.6 4.7": ["degauss"], "7.4 11.6 2.1": ["aparent"], "4.6 18.8 7.6": ["ppls"], "4.3 7.5 14.1": ["smoocher"], "18.2 19.4 24.2": ["congers"], "2.5 -2.1 0.3": ["wekk"], "19.4 29.9 16.5": ["pikemen"], "-0.7 6.6 9.2": ["authori"], "10.0 8.2 1.7": ["druglike"], "8.9 18.3 6.6": ["eulogizers"], "3.1 6.3 12.0": ["stanazolol"], "15.7 8.1 20.2": ["biofactories"], "9.6 18.7 10.6": ["ethanols"], "15.5 5.4 13.8": ["sugardaddy"], "-3.1 1.2 8.3": ["polidocanol"], "10.4 16.2 2.8": ["equaly"], "-4.8 5.2 2.3": ["lamictal"], "8.6 2.7 13.2": ["disconnectable"], "8.8 5.6 2.1": ["reutilized"], "16.3 1.7 14.0": ["flugelhorns"], "-2.4 9.8 14.3": ["lesioned"], "14.9 3.8 36.2": ["murtabak"], "6.9 5.6 8.2": ["pened"], "-0.1 16.2 11.1": ["madala"], "14.5 9.4 16.2": ["portlands"], "2.3 5.2 -0.6": ["sameerb"], "23.2 5.8 15.3": ["leatherware"], "11.3 6.5 20.0": ["kake"], "-0.1 4.9 -4.2": ["coxsackievirus"], "4.7 6.8 5.1": ["metas"], "6.4 13.4 16.7": ["photokeratitis"], "11.7 20.8 23.9": ["attributive"], "9.1 5.3 6.9": ["aicas"], "11.6 8.7 12.1": ["ughh"], "5.5 12.7 9.9": ["flyscreens"], "14.0 7.7 6.4": ["mooncraft"], "3.4 9.1 10.0": ["specturm"], "0.6 23.5 0.7": ["salafism"], "7.9 7.4 21.4": ["waverunners"], "-4.4 6.9 2.5": ["finising"], "2.6 14.5 8.7": ["expirience"], "4.4 24.5 11.3": ["landsmen"], "3.1 12.9 6.8": ["birides"], "10.1 1.0 11.4": ["strongboxes"], "15.1 1.7 7.2": ["constructon"], "1.0 9.0 11.2": ["nalla"], "14.3 5.3 10.4": ["lionshare"], "21.5 19.7 29.9": ["canebrake"], "12.7 6.3 14.0": ["memsahibs"], "9.3 0.8 3.9": ["astrometric"], "5.3 10.9 18.7": ["kamay"], "8.8 4.4 26.3": ["tbls"], "12.0 10.8 3.1": ["geocities"], "20.4 -1.2 25.3": ["hoophouse"], "5.5 13.9 15.9": ["jxknowles"], "10.0 0.7 19.1": ["tacoma"], "11.5 16.9 38.4": ["chironomid"], "3.8 13.8 10.7": ["fronm"], "-1.3 7.8 12.1": ["saaf"], "-3.3 4.1 6.7": ["pigmentosa"], "-4.2 1.0 9.1": ["kainite"], "1.5 0.8 4.7": ["andmarket"], "3.0 7.5 8.6": ["unadapted"], "14.5 5.9 11.7": ["pickaninnies"], "9.0 19.3 1.2": ["aircarft"], "6.1 7.8 16.2": ["officinale"], "0.2 11.2 14.3": ["kinalaman"], "9.1 25.1 10.4": ["walketh"], "-3.5 29.4 0.6": ["mlitary"], "10.0 14.3 13.2": ["bankrobber"], "1.5 17.2 3.2": ["nexts"], "-3.2 9.4 1.1": ["sufferes"], "14.2 6.3 15.6": ["monochord"], "10.6 16.5 5.1": ["xd"], "7.5 1.7 2.4": ["livestreams"], "11.1 22.4 15.6": ["idots"], "7.2 20.5 15.7": ["lboros"], "12.7 16.7 16.7": ["reloader"], "-0.7 0.4 7.2": ["losangeles"], "2.0 7.2 3.0": ["commnity"], "10.4 7.5 13.2": ["waterbuses"], "3.4 11.5 5.6": ["dereference"], "2.6 10.0 7.6": ["togrog"], "-1.2 18.8 7.4": ["mussar"], "-1.2 7.8 16.6": ["midrift"], "-3.9 8.0 6.0": ["performan"], "-3.3 7.0 10.6": ["thillana"], "0.5 16.8 8.9": ["sulfadoxine"], "8.6 -0.8 16.6": ["tonns"], "7.0 -5.3 7.5": ["ibiblio"], "15.3 24.0 2.1": ["monopolism"], "6.6 13.2 12.9": ["deshoukaj"], "2.3 17.5 8.4": ["statespersons"], "-2.5 7.3 1.3": ["plebescite"], "12.1 8.1 9.9": ["mcommerce"], "1.5 24.9 2.3": ["sweared"], "17.6 7.9 13.2": ["biers"], "9.7 1.8 26.9": ["pikake"], "5.6 15.4 5.3": ["agroecosystems"], "10.0 21.6 14.3": ["goooo"], "10.6 1.0 4.9": ["banjolele"], "7.0 3.1 4.1": ["exsiting"], "7.7 3.4 9.9": ["hacen"], "8.3 8.1 12.6": ["umoja"], "9.6 10.5 13.0": ["bady"], "3.9 18.4 11.1": ["referance"], "-1.2 9.3 7.9": ["disbenefit"], "17.8 9.8 21.7": ["unplucked"], "23.8 5.1 5.9": ["suplies"], "5.0 2.9 9.1": ["subcribe"], "-0.4 26.9 9.1": ["supererogatory"], "2.3 8.6 5.6": ["crepitus"], "-6.7 7.8 13.8": ["delive"], "6.6 8.2 14.5": ["dhoop"], "11.2 14.4 8.7": ["screwdriving"], "6.0 16.6 14.6": ["barterers"], "6.9 10.7 15.8": ["warnock"], "10.1 26.1 13.2": ["crucification"], "5.0 8.7 2.9": ["bhavans"], "8.6 1.0 10.6": ["floorlength"], "8.0 12.6 12.2": ["thigs"], "23.6 16.6 12.9": ["forhead"], "8.3 22.4 7.9": ["miraculousness"], "5.3 4.3 11.6": ["phenergan"], "0.5 9.9 4.5": ["liminality"], "9.9 7.5 -1.4": ["pornified"], "9.1 0.1 11.8": ["cutovers"], "4.5 8.4 33.0": ["roasties"], "5.4 15.0 6.3": ["farcial"], "6.2 -1.5 3.5": ["rheometers"], "-0.4 18.1 2.5": ["mentaly"], "-0.8 3.1 6.9": ["diaphoresis"], "5.9 16.8 14.2": ["cjmulrain"], "18.6 24.3 5.9": ["satelites"], "15.6 13.3 17.8": ["kolams"], "13.3 16.2 12.0": ["prostitues"], "5.2 4.7 0.2": ["netbanking"], "10.6 13.6 3.2": ["pasters"], "12.0 12.1 20.3": ["bodkin"], "16.5 8.8 9.9": ["wayfinder"], "12.8 22.5 20.4": ["gimcrackery"], "6.1 2.8 18.4": ["lavoro"], "2.8 13.6 6.2": ["surrebuttal"], "8.3 3.4 4.8": ["acompanied"], "10.4 10.5 11.3": ["hollar"], "5.6 4.0 14.8": ["comprendre"], "5.9 9.1 9.9": ["fastish"], "10.6 4.0 16.8": ["cryoprobe"], "17.9 6.5 25.9": ["bockwurst"], "8.3 9.1 13.6": ["parylene"], "12.1 17.4 16.6": ["bams"], "10.9 7.7 18.0": ["consumtion"], "-0.1 6.8 -3.8": ["idn"], "7.6 6.7 3.8": ["namelist"], "9.5 9.9 11.3": ["tinkerbell"], "7.0 1.8 11.9": ["schols"], "6.9 9.9 7.8": ["immunostimulants"], "0.1 21.0 1.7": ["restablish"], "17.8 10.6 19.5": ["chubbiest"], "10.6 7.7 13.2": ["overshoe"], "-0.3 4.1 8.9": ["wani"], "18.1 8.7 22.9": ["smoochers"], "11.8 2.9 14.2": ["munro"], "14.2 -7.1 18.3": ["peghead"], "8.8 13.8 12.3": ["dactylitis"], "4.8 7.9 10.9": ["uroguanylin"], "0.2 4.5 11.3": ["mendous"], "8.8 7.4 4.7": ["tablespace"], "-5.1 13.2 9.1": ["palmitoylation"], "8.4 12.2 -10.5": ["revealations"], "11.2 17.3 13.8": ["gothically"], "-0.7 6.3 9.3": ["quasispecies"], "15.8 21.8 17.3": ["museumgoer"], "16.2 13.5 22.3": ["guenon"], "-0.4 3.0 10.9": ["canc"], "5.8 11.1 9.6": ["unmended"], "13.2 16.0 7.7": ["efort"], "12.4 3.5 16.2": ["mixmasters"], "18.2 11.3 29.8": ["rijsttafel"], "6.4 23.3 -0.2": ["recoilless"], "13.7 8.6 25.4": ["embarcadero"], "6.0 9.0 2.1": ["deren"], "6.7 22.6 1.4": ["cando"], "8.4 11.8 7.9": ["nanogels"], "-0.0 6.6 7.6": ["sodality"], "19.8 -7.6 4.3": ["millino"], "1.9 0.9 13.2": ["juuust"], "7.6 7.1 6.2": ["telenovellas"], "5.9 2.7 12.9": ["hanover"], "13.6 0.3 8.6": ["iomtoday"], "10.7 6.1 20.0": ["omfg"], "14.6 14.9 6.7": ["stormin"], "5.2 23.6 1.9": ["renditioning"], "11.6 2.6 -0.0": ["tikitag"], "7.1 1.9 3.9": ["suports"], "2.3 9.7 5.2": ["puposes"], "-11.4 16.8 1.2": ["statesmanly"], "6.9 8.9 13.2": ["remainded"], "4.2 8.8 7.5": ["egan"], "14.0 16.6 21.5": ["drooler"], "0.9 3.1 11.5": ["kollu"], "-1.3 34.9 0.6": ["shiites"], "-0.9 3.0 -1.6": ["aleviate"], "-4.4 -0.9 0.7": ["tendent"], "18.1 30.9 4.3": ["missies"], "21.7 6.5 17.0": ["reinjects"], "18.7 17.7 14.6": ["poision"], "10.7 8.0 4.4": ["applys"], "-0.9 0.5 11.2": ["birthparent"], "17.0 9.9 23.3": ["bucketsful"], "18.9 -0.1 9.5": ["pharmeceutical"], "0.4 19.3 6.5": ["unsusceptible"], "17.0 7.6 8.7": ["climing"], "7.1 10.9 10.3": ["escondido"], "7.0 21.4 6.3": ["constructivists"], "5.9 16.1 5.9": ["photosensitiser"], "23.7 19.8 22.3": ["froggies"], "5.0 21.6 -2.5": ["remobilise"], "3.3 9.9 28.6": ["gloxinia"], "1.2 14.6 3.3": ["vivisections"], "1.7 -0.6 3.8": ["freewatt"], "-0.6 6.9 13.8": ["wednesdays"], "-2.1 16.8 10.9": ["juristiction"], "2.1 14.6 3.0": ["embracive"], "22.4 8.5 26.0": ["rimed"], "20.6 12.3 19.7": ["shephard"], "10.3 14.3 10.3": ["hairshirts"], "21.9 7.8 16.0": ["pinnacled"], "19.8 10.6 12.2": ["andenergy"], "13.9 8.6 23.2": ["internode"], "0.2 9.2 20.7": ["montepulciano"], "8.8 15.3 5.4": ["doorhandle"], "2.5 6.1 26.8": ["melony"], "4.6 -3.8 0.1": ["reslizumab"], "-1.0 4.3 6.5": ["outlanding"], "8.1 9.4 1.9": ["disapearance"], "18.3 4.2 4.6": ["supersuite"], "9.2 2.6 18.2": ["isset"], "-7.5 4.0 4.9": ["acedemic"], "-1.8 -3.8 -6.6": ["ssociation"], "5.6 20.4 18.5": ["meitei"], "1.4 -0.5 -3.7": ["gastroplasty"], "0.8 -2.8 6.8": ["nclude"], "7.7 -0.6 3.9": ["ofgovernment"], "8.4 6.8 10.4": ["ummer"], "10.3 14.4 7.8": ["contibuting"], "6.6 8.0 6.0": ["metalloenzymes"], "-7.9 6.5 6.0": ["disannexation"], "17.3 10.0 20.3": ["wellied"], "11.0 13.6 0.4": ["pureblooded"], "7.1 15.6 18.3": ["seedha"], "-0.7 4.5 1.5": ["schreibt"], "9.3 14.7 -0.8": ["wery"], "4.5 15.5 3.8": ["unpredecented"], "1.0 -0.9 7.0": ["urbanizations"], "12.7 10.3 14.4": ["doubletrack"], "-1.8 3.9 0.7": ["concordats"], "-2.5 -0.7 -8.9": ["pointperson"], "-8.9 -9.4 3.5": ["juding"], "12.5 7.6 4.4": ["dolby"], "15.4 -5.6 8.0": ["usps"], "-0.3 16.8 6.3": ["unmanifested"], "-2.2 12.8 9.9": ["comboed"], "15.3 15.4 8.6": ["andmost"], "9.6 12.6 40.2": ["trico"], "-4.0 7.2 13.9": ["pangit"], "1.9 11.9 4.7": ["indunas"], "17.8 1.7 14.5": ["gaushalas"], "13.2 3.2 9.5": ["utilisateur"], "5.4 7.4 6.1": ["parfois"], "8.8 9.6 16.8": ["pajjiz"], "3.3 12.0 2.1": ["erschienen"], "10.5 12.8 15.3": ["hobbing"], "9.0 18.7 12.0": ["bloo"], "3.9 6.3 14.7": ["pinene"], "-2.2 4.0 9.1": ["sidewalkers"], "6.7 14.1 7.8": ["rection"], "7.4 15.3 11.3": ["lattitude"], "15.5 10.3 17.6": ["archosaur"], "1.6 -1.5 2.5": ["commentaires"], "3.8 13.4 9.9": ["heskey"], "18.8 12.7 11.2": ["mismeasured"], "5.0 7.2 27.6": ["tagal"], "6.7 12.5 -0.9": ["selfcontained"], "10.5 16.3 7.6": ["jouney"], "2.8 2.9 2.8": ["annonymity"], "7.2 -5.2 8.3": ["nahcolite"], "13.1 8.9 18.4": ["scagliola"], "7.0 -3.4 4.2": ["discountable"], "6.8 8.3 9.5": ["bleus"], "6.5 6.9 12.6": ["falta"], "9.6 -1.0 4.5": ["nfrastructure"], "-2.5 16.9 3.2": ["appopriate"], "9.4 -2.1 20.7": ["balboa"], "6.9 -2.0 2.5": ["solidbody"], "-3.4 8.5 7.2": ["thatmay"], "1.8 -1.4 7.1": ["cryoplasty"], "6.2 5.7 7.6": ["microlasers"], "-1.1 11.0 14.6": ["waller"], "-1.3 5.5 8.8": ["photoactivation"], "5.6 14.3 5.8": ["tattooer"], "14.2 -4.8 1.5": ["majaps"], "13.8 6.7 -1.7": ["cientists"], "3.3 -5.9 2.1": ["annualmeeting"], "9.0 14.4 7.7": ["sulkers"], "2.3 10.3 8.4": ["yiddishkeit"], "2.2 10.1 2.5": ["hlp"], "-1.6 9.8 4.0": ["converation"], "-1.7 9.4 6.4": ["microampere"], "-1.7 -8.4 3.6": ["annualisation"], "4.1 1.6 2.4": ["tday"], "9.5 24.4 15.5": ["karstic"], "-4.1 1.5 15.1": ["lins"], "4.8 3.6 7.4": ["copie"], "-0.3 -1.1 12.8": ["subalit"], "8.0 10.6 6.0": ["telecentric"], "0.2 -3.9 -6.6": ["wthin"], "5.6 8.6 14.7": ["davao"], "11.2 5.5 4.9": ["competititve"], "6.7 3.0 8.8": ["weatherable"], "-4.1 3.6 2.4": ["mydriasis"], "-1.8 5.7 8.7": ["transations"], "0.8 -2.8 14.4": ["orchidectomy"], "-5.8 6.2 14.3": ["pangyayari"], "1.4 6.4 18.6": ["crackingly"], "1.8 12.5 7.3": ["gast"], "13.5 12.7 12.6": ["lucifer"], "11.6 2.1 8.4": ["biothermal"], "2.4 15.1 10.2": ["poachings"], "4.7 1.0 11.1": ["comi"], "5.5 9.2 12.7": ["tubo"], "2.7 5.7 5.9": ["ticos"], "1.4 -8.7 13.2": ["postbaccalaureate"], "-4.0 -2.5 9.8": ["averag"], "-0.2 7.6 0.8": ["thrd"], "11.0 10.5 2.9": ["lifecast"], "0.8 7.4 10.9": ["unmelodic"], "5.1 2.8 13.7": ["mensa"], "-5.0 10.8 3.1": ["electio"], "16.1 11.0 9.1": ["vulcanizer"], "-1.2 12.9 2.8": ["tiagabine"], "9.2 9.2 17.2": ["ratite"], "7.8 3.3 5.0": ["amf"], "4.7 17.1 8.0": ["talwar"], "7.5 14.5 7.1": ["perhpas"], "4.7 2.3 5.0": ["rejuvenative"], "5.0 9.1 8.7": ["fluorogenic"], "6.1 8.4 17.5": ["tator"], "8.6 2.8 3.3": ["twidroyd"], "18.7 3.7 27.7": ["vanda"], "-0.1 -4.2 1.7": ["fhios"], "2.6 11.6 6.9": ["bhaichara"], "6.6 8.3 12.4": ["furter"], "24.8 15.0 29.7": ["jackalopes"], "-5.6 9.3 2.7": ["noncurricular"], "13.4 11.3 19.9": ["downshifters"], "10.6 2.2 19.0": ["gant"], "8.9 5.0 10.3": ["considera"], "9.4 0.8 10.9": ["principalmente"], "10.1 15.2 9.7": ["culdesac"], "5.7 7.0 15.6": ["clorgyline"], "3.1 19.8 16.2": ["onliest"], "12.9 9.8 28.6": ["almondy"], "3.8 -2.9 12.2": ["regionale"], "19.2 13.3 29.1": ["shuckin"], "5.9 9.5 6.7": ["mainpage"], "11.3 8.1 16.1": ["siga"], "5.8 -8.9 -0.2": ["qbr"], "12.8 9.8 9.8": ["autowallahs"], "9.5 15.3 9.6": ["kepi"], "4.8 11.2 9.4": ["takht"], "6.3 -1.9 15.7": ["sosyal"], "16.2 6.7 24.1": ["menues"], "-4.8 15.9 6.7": ["derserve"], "2.7 13.0 8.3": ["adrenoceptor"], "11.4 0.8 21.4": ["drinkies"], "7.5 21.0 18.6": ["hantu"], "2.3 0.1 17.3": ["classers"], "18.9 8.1 24.6": ["windowboxes"], "7.1 26.7 19.7": ["getout"], "-7.0 14.4 -1.8": ["observor"], "6.5 15.2 7.6": ["systemising"], "5.7 7.4 3.5": ["telestration"], "5.7 13.3 12.0": ["bluffland"], "10.0 8.3 14.3": ["minha"], "7.5 8.5 13.9": ["carly"], "3.3 9.8 16.9": ["thema"], "7.8 11.5 10.8": ["hazaar"], "3.0 1.4 7.6": ["brods"], "8.1 18.3 17.0": ["dethatch"], "16.8 14.5 7.8": ["generica"], "3.4 10.7 18.5": ["husbandless"], "-1.1 4.5 3.0": ["indegenes"], "1.8 16.1 3.1": ["denegrate"], "17.8 11.2 15.7": ["waco"], "9.1 28.1 9.2": ["wussiness"], "19.0 2.1 11.6": ["seeling"], "18.9 13.8 23.6": ["maculata"], "3.1 -3.5 -6.9": ["andindustry"], "-1.8 15.0 6.4": ["networx"], "11.1 9.3 12.0": ["snortin"], "11.8 11.1 9.2": ["oubreak"], "-8.2 7.9 7.2": ["investigaiton"], "2.1 16.8 10.5": ["resurrectionists"], "13.1 5.2 28.2": ["gillie"], "1.4 15.4 3.9": ["seminally"], "1.1 -7.2 7.8": ["spiritleaders"], "3.9 11.7 14.9": ["olivines"], "-0.9 4.9 9.8": ["passess"], "1.3 -4.4 -2.3": ["culturel"], "6.9 -0.8 7.5": ["concernant"], "2.6 12.4 13.6": ["gooo"], "2.8 2.7 9.5": ["retrovirals"], "3.2 16.8 12.9": ["tommyrot"], "11.3 11.4 14.8": ["foiler"], "13.0 9.5 16.7": ["ghostliness"], "-1.7 22.1 10.5": ["firsties"], "3.3 5.6 17.4": ["bodi"], "5.4 2.0 14.7": ["biphenyls"], "4.1 9.4 19.7": ["tatakbo"], "10.3 5.5 5.7": ["budhiya"], "0.6 4.9 2.9": ["seconed"], "3.1 9.0 10.8": ["rebroken"], "7.9 11.7 16.4": ["participantes"], "7.8 14.2 7.1": ["floodproof"], "12.4 15.1 5.1": ["diffracting"], "3.3 3.0 4.4": ["wiould"], "14.4 7.1 7.3": ["piconewtons"], "3.7 13.5 5.7": ["insan"], "12.8 5.4 1.9": ["marekt"], "5.3 11.0 6.8": ["econonmy"], "10.3 14.6 20.9": ["radicans"], "3.3 19.6 9.5": ["unwarrantable"], "24.2 11.2 5.0": ["pintsized"], "1.2 3.0 17.9": ["kagabi"], "0.9 9.9 11.9": ["pocketpc"], "-2.4 0.6 10.8": ["miniscus"], "21.0 9.5 31.3": ["toothier"], "1.1 5.0 9.2": ["nitrazepam"], "9.5 13.2 12.6": ["polyline"], "15.2 10.2 4.5": ["diatomic"], "-1.6 -2.0 9.7": ["sitions"], "14.0 8.2 4.6": ["electronvolts"], "-1.2 1.2 1.5": ["financeability"], "24.3 20.9 20.4": ["piton"], "8.7 12.4 12.0": ["chinars"], "2.2 6.3 7.2": ["bloodpressure"], "-3.5 1.4 2.9": ["psychogeriatric"], "17.6 3.4 -0.6": ["umpc"], "19.8 20.7 11.7": ["eyehole"], "8.8 0.8 20.4": ["lumbermill"], "5.1 2.2 13.7": ["fivemonth"], "6.7 22.3 12.1": ["bookin"], "-5.5 -0.8 -1.6": ["lipohypertrophy"], "9.7 5.2 1.2": ["mischarged"], "22.4 12.8 26.4": ["cryptomeria"], "16.3 -1.0 14.7": ["coolings"], "4.9 4.6 5.3": ["awin"], "9.1 10.9 11.6": ["polymerised"], "3.6 -0.6 -0.3": ["aventure"], "10.3 7.3 24.5": ["fisho"], "2.0 9.3 6.7": ["absolut"], "16.6 13.4 8.0": ["azy"], "16.4 6.4 14.9": ["tailwhips"], "10.5 7.6 18.5": ["shuv"], "6.3 8.5 8.8": ["environemnt"], "17.9 12.5 14.1": ["whena"], "16.0 14.7 23.3": ["scurf"], "6.9 3.5 6.9": ["embolectomy"], "0.0 10.6 1.7": ["scanlations"], "-1.1 19.1 11.2": ["athleticsm"], "17.2 5.1 5.2": ["switchoff"], "17.3 0.7 10.8": ["shawm"], "-3.6 2.7 3.5": ["dividual"], "11.7 20.0 17.2": ["bracers"], "0.7 11.6 10.6": ["ascetically"], "13.7 18.5 23.0": ["brainworm"], "4.8 11.3 4.3": ["mertansine"], "0.4 -7.6 0.4": ["thefive"], "15.5 12.6 15.9": ["corporatespeak"], "14.5 5.6 13.1": ["nongreen"], "0.3 13.4 6.4": ["maling"], "0.9 13.1 5.0": ["crossfit"], "-1.9 11.7 10.3": ["sfc"], "-4.9 10.7 4.9": ["glycosyltransferase"], "12.5 16.7 4.2": ["downsizer"], "-1.4 14.5 5.0": ["differerent"], "5.5 16.7 10.9": ["hondo"], "6.3 9.8 1.3": ["roadcar"], "-5.2 0.9 6.1": ["ionophore"], "11.7 8.2 4.0": ["nearfield"], "3.5 14.8 6.4": ["tuberculoses"], "-0.4 11.9 10.6": ["charanam"], "27.6 17.0 14.8": ["spining"], "23.2 17.1 20.6": ["arachnophobes"], "3.6 7.3 28.1": ["pummelos"], "17.1 13.2 12.4": ["apodeiterium"], "4.1 1.3 6.4": ["charitys"], "16.1 9.1 12.0": ["intelli"], "14.3 -6.7 8.2": ["wynn"], "9.9 9.4 18.1": ["sumotori"], "7.4 23.5 12.1": ["submachinegun"], "-2.2 7.7 3.2": ["transnasal", "immunoregulation"], "28.9 8.2 35.3": ["polliwogs"], "-0.2 -1.3 6.3": ["aun"], "0.3 9.9 12.8": ["unrentable"], "13.4 11.2 10.2": ["steelmen"], "-0.3 3.0 -1.5": ["probono"], "4.9 16.0 10.7": ["paniced"], "8.5 1.1 -1.4": ["actigraphs"], "-4.9 3.0 7.7": ["tumse"], "-0.3 7.4 9.0": ["intefere"], "7.4 12.1 9.9": ["megadonors"], "13.4 8.7 -0.2": ["midfiedler"], "8.6 28.1 11.2": ["gamemanship"], "0.8 18.3 8.8": ["autoreactive"], "20.0 7.5 12.0": ["georgeous"], "-2.1 20.4 0.1": ["hijaab"], "-4.1 14.4 5.2": ["mard"], "5.9 6.6 4.1": ["alaskites"], "10.0 1.1 3.5": ["agreemen"], "14.8 3.3 13.2": ["hancock"], "3.7 13.2 15.3": ["antimycin"], "13.0 3.5 32.0": ["onglet"], "4.7 0.5 11.5": ["dday"], "1.5 -1.2 8.2": ["thenon"], "2.1 -2.7 7.7": ["dianabol"], "-6.2 17.6 2.2": ["confidentialities"], "5.6 6.7 9.6": ["rooky"], "8.6 -3.8 19.1": ["couche"], "5.8 5.8 12.3": ["ungentrified"], "7.9 5.5 9.8": ["sqmt"], "-8.1 -1.2 -1.5": ["recei"], "3.3 8.2 -8.4": ["inititatives"], "13.8 5.1 21.7": ["myotis"], "4.5 6.4 10.1": ["pleconaril"], "8.5 1.0 31.2": ["membrillo"], "-0.2 -2.8 11.0": ["trah"], "27.9 11.7 14.9": ["earthlike"], "9.9 10.8 6.1": ["streamling"], "-0.4 4.5 3.2": ["rales"], "8.5 17.0 44.2": ["turnstones"], "11.4 25.0 5.7": ["theopposition"], "1.1 4.1 8.0": ["overtuned"], "8.2 1.6 14.0": ["rubin"], "10.8 11.3 13.8": ["arth"], "5.1 10.8 2.0": ["memorialisation"], "8.6 7.2 29.0": ["nuong"], "3.1 27.0 0.7": ["complot"], "5.4 -0.8 16.6": ["resham"], "-2.3 -3.9 11.8": ["tains"], "9.2 5.7 13.9": ["flangeless"], "8.6 6.5 7.9": ["conduciveness"], "14.8 23.4 26.3": ["nonillion"], "12.6 10.6 19.4": ["taxus"], "6.7 0.6 12.8": ["condiciones"], "5.6 -2.4 2.2": ["thetechnology"], "7.9 6.2 5.2": ["ien"], "11.8 13.0 4.9": ["cossetting"], "3.4 -1.1 -3.4": ["udpate"], "5.3 11.2 17.8": ["scrofula"], "15.9 11.1 29.4": ["kahikatea"], "8.1 5.6 -1.2": ["midfieder"], "-4.0 8.3 10.8": ["regrant"], "2.3 2.5 12.3": ["batla"], "7.3 19.6 14.6": ["spinorama"], "8.5 13.1 3.9": ["thenetwork"], "1.2 10.4 11.0": ["couldas"], "2.1 17.3 -3.9": ["chalenge"], "1.7 10.8 11.3": ["magnanakaw"], "14.7 19.3 1.3": ["eminate"], "-2.0 1.5 2.6": ["reintubation"], "17.3 10.2 37.3": ["corella"], "14.9 18.3 1.7": ["stargates"], "25.0 15.9 13.6": ["sawblade"], "12.2 6.2 10.1": ["parps"], "-1.0 -7.0 1.3": ["ements"], "21.0 29.3 13.5": ["schnooks"], "12.9 17.3 10.6": ["hamba"], "11.1 6.1 9.4": ["tabloidism"], "9.6 10.9 8.8": ["readably"], "-0.7 -4.7 -4.5": ["victoy"], "4.2 -0.1 14.9": ["deliquescence"], "6.1 8.9 29.5": ["tinola"], "15.5 6.0 11.1": ["creatin"], "2.1 9.2 17.6": ["bayani"], "9.1 5.0 -1.8": ["gooned"], "2.2 7.4 9.0": ["mutexes"], "4.7 13.6 5.6": ["thatwere"], "3.6 5.5 8.1": ["guten"], "15.3 4.5 25.4": ["pulla"], "-4.6 13.9 2.5": ["madarasas"], "6.6 6.4 -3.9": ["poleaxing"], "6.7 15.8 10.8": ["nurturant"], "7.6 16.8 20.2": ["cides"], "1.3 5.6 8.7": ["adt"], "8.6 5.2 34.2": ["cattleyas"], "-0.2 3.6 1.5": ["administative"], "1.1 8.8 11.3": ["kharab"], "2.9 10.1 16.2": ["fitsnews"], "6.1 -2.1 1.2": ["simillar"], "12.9 7.7 13.7": ["utan"], "14.1 3.9 8.4": ["megaupload"], "8.7 5.0 17.1": ["uto"], "12.4 16.5 23.8": ["lebkuchen"], "4.4 10.4 14.1": ["respired"], "21.0 18.1 22.5": ["spyglasses"], "-2.6 -0.7 2.6": ["udge"], "2.1 -5.8 2.0": ["arv"], "12.9 12.5 10.4": ["illwill"], "13.4 3.2 12.6": ["vulcanising"], "-1.1 -0.6 -3.7": ["ncy"], "19.9 9.7 20.6": ["frenching"], "6.8 16.4 11.7": ["ofen"], "-3.7 15.7 8.0": ["leaderhsip"], "5.5 1.8 5.6": ["alimentaire"], "12.5 37.4 9.5": ["planetside"], "4.4 4.5 16.6": ["pennyweights"], "19.9 5.3 42.6": ["razorfish"], "5.4 31.9 8.5": ["impune"], "1.1 0.1 -2.0": ["dauther"], "1.1 5.0 10.3": ["andthis"], "11.5 3.9 34.0": ["pooris"], "21.4 6.4 9.6": ["screwiest"], "9.8 3.5 19.8": ["jusi"], "-1.3 0.8 4.6": ["thusa"], "6.9 11.5 14.2": ["waah"], "7.6 -1.4 6.1": ["theprintspace"], "5.3 12.4 13.6": ["sankranti"], "0.8 4.5 26.7": ["ginjo"], "-3.5 3.6 11.0": ["pahayag"], "-3.2 22.7 0.3": ["politicaly"], "19.5 2.1 9.3": ["poohbah"], "14.4 -0.6 19.0": ["overcap"], "15.0 26.5 21.4": ["homosapiens"], "1.2 16.8 12.1": ["forecaddies"], "6.8 19.7 18.5": ["mandelbrot"], "3.8 13.6 7.6": ["checkgate"], "12.8 16.6 8.1": ["depressurise"], "16.0 20.1 9.9": ["enkindled"], "2.2 -4.4 9.7": ["pss"], "9.8 11.0 16.4": ["shap"], "2.7 5.0 12.2": ["diastema"], "12.0 10.0 22.8": ["grimes"], "6.4 13.8 12.6": ["crimebook"], "7.8 3.8 6.2": ["beadlock"], "4.5 0.3 3.2": ["dior"], "1.2 3.0 6.8": ["prosthodontic"], "12.1 3.4 -0.3": ["anuncia"], "-6.0 12.4 4.1": ["oout"], "22.0 7.5 23.3": ["rassle"], "10.6 29.2 16.4": ["aresenal"], "4.5 -0.2 6.5": ["subdivsion"], "9.3 4.4 4.1": ["copia"], "12.7 5.4 5.0": ["pixyish"], "21.0 4.7 -0.4": ["manufaturing"], "10.6 3.3 16.1": ["sipa"], "8.9 -7.7 4.2": ["tugrik"], "5.6 4.4 7.7": ["langauges"], "11.9 3.4 14.7": ["penney"], "10.4 15.8 10.6": ["lieberman"], "8.2 20.3 -2.0": ["bluesnarfing"], "7.0 12.5 17.5": ["naptimes"], "8.2 17.7 2.7": ["wiretapper"], "10.5 13.2 9.1": ["entites"], "7.7 22.5 5.3": ["tenous"], "8.4 9.8 7.3": ["funkateers"], "6.5 4.5 8.2": ["molex"], "8.2 -7.5 1.4": ["inceased"], "18.3 8.5 5.6": ["disected"], "1.0 4.9 6.7": ["schoolgoers"], "5.4 2.8 11.6": ["methaphetamine"], "18.9 4.5 13.3": ["kissa"], "-0.8 13.0 13.9": ["lysin"], "11.7 9.9 18.7": ["golddiggers"], "-0.5 9.0 0.9": ["prope"], "9.6 8.7 3.0": ["agsinst"], "3.6 12.0 15.5": ["laal"], "11.4 14.7 9.3": ["deeping"], "11.8 12.5 19.0": ["balll"], "-0.0 5.7 22.5": ["intinction"], "22.0 4.1 18.9": ["foamcore"], "5.3 19.3 -6.4": ["involment"], "18.2 3.9 6.1": ["ikon"], "-1.3 9.5 14.1": ["khela"], "13.3 19.7 11.5": ["maddness"], "11.6 16.0 4.6": ["curiousness"], "8.6 8.9 1.5": ["charac"], "12.4 28.5 13.9": ["mankinds"], "-0.6 15.4 11.2": ["descisions"], "15.9 12.5 17.0": ["curmudgeonliness"], "10.1 2.5 6.2": ["represen"], "33.5 1.9 25.3": ["pteranodon"], "16.2 20.5 17.9": ["clumpiness"], "-3.3 6.8 4.5": ["normothermic"], "7.6 7.4 9.0": ["unremediated"], "-5.4 0.4 10.3": ["fih"], "-1.5 2.9 6.7": ["baugh"], "12.3 14.4 18.3": ["shrublike"], "18.7 10.7 6.8": ["nascency"], "-1.1 15.5 2.9": ["inprove"], "12.5 4.0 4.2": ["bloodgate"], "2.9 10.4 10.0": ["etchant"], "-0.4 -3.3 1.1": ["issus"], "-1.5 0.2 12.6": ["principalement"], "3.0 3.5 6.0": ["inproved"], "6.1 -2.1 9.3": ["modelo"], "4.3 4.9 5.2": ["vitespen", "multiepisode"], "17.3 9.0 17.6": ["superlab"], "9.0 20.0 3.3": ["clammoring"], "2.9 1.3 16.9": ["naturel"], "7.7 24.1 9.4": ["belatedness"], "14.0 8.0 13.2": ["bandar"], "4.4 4.3 4.3": ["burroughs"], "4.4 -1.8 -2.1": ["thegrowing"], "16.1 7.4 5.3": ["jfk"], "15.2 6.0 9.1": ["technol"], "6.8 2.7 9.2": ["busca"], "-2.6 6.8 -6.3": ["publicsafety"], "4.8 14.3 9.0": ["stricker"], "7.1 16.7 -0.1": ["seriouly"], "10.8 15.8 13.1": ["scrilla"], "5.0 19.9 -0.2": ["arabization"], "-2.1 6.2 11.5": ["fede"], "2.5 -4.5 2.3": ["anton"], "20.2 8.4 30.0": ["canela"], "1.7 7.4 11.4": ["hoti"], "9.2 -0.2 34.1": ["kimjang"], "7.0 7.5 2.5": ["submiting"], "9.9 11.1 3.5": ["misdialled"], "5.1 12.8 21.7": ["cuppy"], "18.5 9.5 14.6": ["teenybop"], "5.7 6.5 -1.2": ["tractography"], "-1.6 3.5 -3.3": ["losed"], "17.6 13.8 9.5": ["kipped"], "-8.0 5.2 0.6": ["anwered"], "0.9 14.1 11.2": ["handeling"], "8.8 13.5 8.3": ["manoevre"], "14.4 11.0 14.9": ["nonscary"], "13.0 5.3 24.7": ["laevis"], "6.7 5.9 7.7": ["trg"], "7.5 0.5 21.2": ["paka"], "-17.6 16.9 -10.4": ["leadeship"], "16.8 7.1 12.1": ["chuffs"], "25.9 11.5 24.2": ["spil"], "20.3 7.6 30.1": ["birdfeed"], "8.4 -1.0 9.1": ["summmit"], "3.4 12.0 8.9": ["heathrow"], "-1.1 8.2 14.8": ["catagorized"], "16.2 4.8 12.6": ["sparkies"], "14.3 10.1 19.6": ["restoratives"], "3.2 12.9 4.4": ["infi"], "5.6 0.7 10.5": ["veranderingen"], "4.6 9.9 -0.2": ["beetween"], "14.0 11.4 14.6": ["rassler"], "4.1 17.9 0.2": ["agrument"], "11.5 21.0 3.2": ["iteself"], "3.5 2.5 2.6": ["intradiscal"], "-17.1 -9.8 -2.3": ["eligibly"], "-0.2 -0.3 7.9": ["emirati"], "3.9 4.1 11.6": ["lumican"], "-3.1 -3.8 12.5": ["inm"], "14.9 11.7 10.2": ["fems"], "15.4 1.7 6.7": ["uncapitalized"], "9.8 5.8 9.7": ["countercultures"], "1.9 8.9 8.1": ["asse"], "12.5 16.7 21.2": ["prarie"], "4.1 6.7 12.3": ["fibromatosis"], "0.8 6.8 9.7": ["volves", "yatrees"], "18.3 5.6 24.8": ["cevapcici"], "3.5 4.6 6.7": ["coference"], "1.6 6.3 17.7": ["fleming"], "19.9 5.0 26.9": ["earthtones"], "-3.1 11.9 10.0": ["finalities"], "3.0 8.8 11.4": ["matalo"], "7.4 17.5 10.7": ["ctually"], "0.2 4.0 7.4": ["gaba"], "9.5 0.0 13.6": ["performanced"], "5.6 5.9 9.6": ["overspeculation"], "5.4 7.1 20.9": ["franca"], "6.9 5.3 8.2": ["gameagainst"], "-3.7 4.0 -2.5": ["fibrinolytics"], "6.8 23.0 13.5": ["scatbacks"], "-4.5 13.9 10.0": ["ofboth"], "5.3 4.0 7.0": ["spermine"], "-7.3 2.4 6.2": ["pretrip"], "5.7 10.7 11.9": ["aami"], "10.5 20.5 14.7": ["pluralization"], "23.6 4.8 11.2": ["sharebroking"], "10.7 8.7 5.0": ["immunizers"], "14.1 19.7 13.9": ["gustily"], "9.6 9.7 11.2": ["bioprinting"], "4.7 7.6 10.0": ["rhytids"], "0.1 26.6 9.7": ["bastardly"], "14.5 14.7 10.5": ["drawnout"], "3.5 14.0 13.9": ["asure"], "10.6 8.9 19.3": ["turbulant"], "11.4 19.0 13.8": ["scap"], "0.4 3.4 6.1": ["cablecasters"], "5.9 6.2 17.8": ["overo"], "-2.5 11.9 6.4": ["roverback"], "10.6 -4.3 5.2": ["kwik"], "-0.1 7.9 18.0": ["secound"], "9.3 12.7 15.3": ["paytables"], "4.7 -4.3 13.7": ["xam"], "3.9 19.8 20.8": ["mappy"], "7.7 9.7 11.2": ["lithographically"], "7.3 12.7 1.5": ["goalpoacher"], "-7.4 18.2 -7.3": ["unbiasedly"], "13.3 -4.9 18.7": ["rebond"], "1.8 9.2 5.5": ["megasonics"], "-6.4 -1.9 -4.7": ["pubbed"], "16.2 12.8 15.4": ["bloatedness"], "10.1 10.1 18.6": ["meyers"], "12.7 17.0 27.6": ["microbats"], "3.6 16.5 8.8": ["kshatriya"], "0.1 -5.9 7.3": ["quickturn"], "10.3 7.3 3.3": ["inaugeration"], "-2.1 3.6 5.9": ["wyn"], "8.3 11.7 5.2": ["popculture"], "6.3 18.3 8.1": ["anwhere"], "6.7 4.9 2.6": ["overinflation"], "8.0 5.0 -4.1": ["powerpacks"], "6.9 9.6 16.8": ["bursae"], "9.4 15.0 9.4": ["amorally"], "0.4 20.5 4.5": ["arguendo"], "3.4 13.6 8.4": ["abraham"], "17.2 16.0 30.6": ["spincasting"], "-1.5 11.3 15.7": ["stepgrandchild"], "9.8 8.3 2.6": ["nanofabricated"], "-3.7 16.0 8.2": ["outbatted"], "-4.4 6.0 11.7": ["nasha"], "12.1 1.5 15.4": ["packeted"], "-4.7 5.3 5.3": ["adipogenic"], "7.8 12.0 3.1": ["vitalising"], "0.4 1.6 16.6": ["pearce"], "7.2 9.6 14.7": ["iska"], "9.8 7.5 15.2": ["dojis"], "-0.2 2.1 7.2": ["awf"], "4.3 16.0 8.7": ["refugess"], "0.6 8.6 13.0": ["mamaya"], "24.7 16.0 5.9": ["moghuls"], "21.9 10.6 18.8": ["nonabsorbent"], "11.9 2.5 3.8": ["nbbc"], "-1.9 14.5 9.5": ["sinlessness"], "7.2 11.9 12.2": ["witched"], "15.8 11.0 20.8": ["clorox"], "2.3 0.8 5.4": ["unbillable"], "6.6 23.6 14.0": ["assclowns"], "3.0 22.9 -0.8": ["retailiation"], "16.9 18.6 8.7": ["handwaving"], "10.8 -0.3 8.0": ["estadounidenses"], "7.1 10.5 12.7": ["mither"], "-0.0 -7.1 18.4": ["primeurs"], "12.8 12.4 10.9": ["canali"], "2.7 2.9 -0.6": ["aciduria"], "3.6 6.2 2.9": ["oficiales"], "5.8 7.8 17.7": ["contrarion"], "2.5 10.6 16.6": ["russo"], "17.0 6.9 15.0": ["sphynx"], "4.6 2.5 11.3": ["bizzy"], "8.3 1.1 10.7": ["outsourcees"], "6.9 10.8 5.0": ["quia"], "16.1 21.6 12.7": ["unfestive"], "20.4 4.7 15.4": ["tomahto"], "9.4 16.2 7.0": ["makng"], "7.4 5.0 6.0": ["pesar"], "10.4 13.4 15.0": ["yadda"], "9.2 10.4 13.8": ["buttonhook"], "-0.4 6.5 8.5": ["actvity"], "4.5 2.4 4.4": ["extemporizing"], "4.6 14.2 4.0": ["guantanamo"], "11.6 20.9 11.9": ["pericentre"], "2.0 10.4 10.9": ["formguide"], "14.1 7.6 11.8": ["seismography"], "-0.0 12.7 11.0": ["fliering"], "11.4 13.3 9.0": ["zajal"], "5.3 0.6 17.0": ["nauna"], "10.5 5.9 18.4": ["unq"], "5.8 1.3 0.8": ["formulative"], "10.5 0.2 2.7": ["thecontract"], "6.9 11.4 2.5": ["csu"], "10.8 -7.4 17.9": ["trashion"], "4.1 3.0 3.5": ["boardless"], "15.4 -1.0 0.4": ["ises"], "5.7 9.6 23.0": ["tabo"], "-2.4 2.5 5.7": ["dismised"], "4.6 33.5 15.2": ["medivacs"], "19.7 25.4 24.1": ["unraked"], "-0.4 9.5 1.6": ["patriarchates"], "2.4 10.6 9.1": ["anticruelty"], "4.7 5.8 2.3": ["strategie"], "5.5 13.7 5.9": ["proteinases"], "2.6 -1.2 -5.7": ["fiberscopes"], "-5.6 13.3 2.9": ["chasidim"], "-0.9 4.0 10.1": ["talkier"], "4.4 16.8 9.6": ["satisfier"], "11.2 8.6 15.5": ["colbert"], "9.3 13.8 5.2": ["consciouness"], "-6.5 -3.0 1.4": ["anaysis"], "5.1 9.1 16.0": ["kikay"], "8.8 -0.8 -1.7": ["pressline"], "-0.9 10.3 4.1": ["lengthiness"], "8.9 12.5 16.9": ["bilaterians"], "12.0 12.8 14.7": ["wlan"], "17.1 11.0 12.2": ["neuromorphic"], "11.8 9.2 6.8": ["athleticwear"], "2.5 17.7 7.7": ["lifehacker"], "0.7 5.3 3.8": ["chronogram"], "0.5 9.7 13.2": ["anough"], "13.5 -3.2 10.3": ["tramite"], "9.4 3.5 -0.7": ["blockbluster"], "10.4 4.5 35.0": ["gratinee"], "12.9 4.6 -0.4": ["sysem"], "14.2 9.1 33.8": ["pulpo"], "10.2 17.7 1.3": ["westernise"], "8.0 13.1 2.1": ["ird"], "20.2 16.2 15.3": ["dicers"], "20.6 32.7 17.0": ["sackboy"], "-2.3 1.2 3.3": ["norpseudoephedrine"], "12.2 34.2 8.6": ["uncontrollability"], "11.1 16.8 8.7": ["redonkulous"], "6.6 11.5 14.5": ["dendro"], "5.0 -0.5 9.8": ["enbloc"], "10.7 -0.2 -1.2": ["demutualizing"], "5.4 5.5 14.4": ["yb"], "6.1 10.7 17.6": ["anticarcinogenic"], "12.1 16.9 23.8": ["iceplant"], "-4.5 9.9 7.0": ["propertys"], "7.6 0.5 14.8": ["krai"], "15.3 3.5 4.3": ["auctioner"], "6.8 27.6 6.7": ["toxification"], "3.0 11.5 8.8": ["baxter"], "7.0 2.8 20.4": ["ligero"], "10.2 14.8 1.5": ["videocall"], "10.2 2.9 9.0": ["bpp"], "9.0 10.7 -1.5": ["infostructure"], "-1.4 4.7 17.4": ["malamang"], "-4.8 -5.0 -6.2": ["therelease"], "-2.2 -3.4 6.4": ["disucssion"], "12.3 10.4 28.9": ["echeveria"], "-4.2 10.6 8.9": ["hona"], "0.2 11.3 2.4": ["gaurav"], "-0.9 5.1 -10.1": ["apppeared"], "6.4 8.4 5.4": ["arbeiten"], "8.0 -4.3 4.3": ["bioprosthetic"], "7.3 9.9 8.9": ["rockabillies"], "5.9 1.0 8.3": ["wahs"], "4.8 -4.6 0.6": ["informaticists"], "9.1 10.2 37.0": ["driftboats"], "21.8 6.3 7.6": ["precessing"], "1.9 7.0 0.3": ["officilas"], "-0.1 5.1 8.7": ["phenothiazines"], "-2.3 10.4 6.9": ["homodimers"], "12.4 0.1 12.4": ["musicfest"], "9.1 1.0 8.9": ["fluorosilicone"], "20.8 10.2 8.5": ["shorlty"], "-2.3 3.9 3.4": ["brimonidine"], "7.6 6.6 15.1": ["gollies"], "1.8 16.7 7.5": ["ngoba"], "5.5 8.2 13.7": ["gaushala"], "2.1 15.0 14.0": ["phytates"], "8.8 6.7 22.9": ["replantings"], "24.7 4.4 11.9": ["hangarlike"], "4.4 -1.1 -0.7": ["pect"], "1.4 12.1 11.4": ["hammier"], "14.6 15.5 15.1": ["mazel"], "-1.7 -0.0 9.5": ["sio"], "19.3 3.5 26.0": ["unground"], "9.1 3.6 -0.1": ["xyzmo"], "4.6 6.1 22.7": ["bagets"], "3.2 0.2 5.9": ["refere"], "12.3 14.4 12.0": ["urned"], "3.1 1.4 -5.5": ["tittled"], "8.0 5.8 9.0": ["sette"], "21.4 10.4 20.5": ["unmown"], "-6.6 1.0 3.2": ["involoved"], "9.6 9.5 9.5": ["dessus"], "2.9 -2.8 8.4": ["ferroniobium"], "0.1 7.5 11.9": ["bastnasite"], "-1.1 3.6 10.7": ["majlises"], "13.8 12.9 7.8": ["fap"], "1.8 4.0 7.3": ["iva"], "-10.1 14.1 1.7": ["kodesh"], "7.4 -4.4 3.3": ["euroscript"], "13.7 19.4 7.2": ["pixeled"], "18.3 8.6 9.3": ["cognescenti"], "-6.3 8.8 12.5": ["deyr"], "15.2 13.6 4.5": ["superatoms"], "14.9 26.6 17.0": ["lingerer"], "8.3 12.7 25.8": ["colchicum"], "12.8 3.4 16.7": ["willinclude"], "-4.5 -1.0 5.7": ["remittal"], "6.6 1.1 6.2": ["relend"], "12.9 -2.8 12.0": ["ammolite"], "3.0 19.2 -1.3": ["dominionists"], "10.1 6.7 7.8": ["libros"], "2.9 12.4 6.9": ["immitis"], "8.6 11.1 8.3": ["degraders"], "17.7 6.6 13.4": ["horsetrack"], "5.7 5.6 16.8": ["maurice"], "16.8 5.6 18.0": ["copperware"], "0.3 12.2 14.1": ["amorousness"], "8.0 17.1 13.7": ["hypergolic"], "-7.5 16.4 -0.5": ["corss"], "15.4 15.8 16.7": ["wimpering"], "2.9 14.5 13.2": ["coverture"], "7.2 25.7 14.3": ["goonies"], "5.0 6.1 15.8": ["lleva"], "5.0 -0.2 2.0": ["tahasildar"], "-1.4 12.3 10.6": ["dnc"], "1.2 13.1 1.1": ["backflush"], "10.6 20.9 14.9": ["amazonian"], "4.6 4.8 7.2": ["conseuctive"], "13.3 22.9 7.6": ["toxify"], "6.5 25.1 12.6": ["hiddenness"], "17.6 27.0 10.8": ["pockmarking"], "6.7 7.7 2.6": ["reannouncing"], "21.8 8.7 13.3": ["microcompartments"], "-5.3 12.2 -0.0": ["subsec"], "3.6 8.6 24.2": ["diascia"], "8.6 30.3 10.5": ["delegitimate"], "13.8 13.7 16.0": ["hoodied"], "-9.2 -2.4 8.9": ["rearraignment"], "14.6 11.3 24.1": ["jaali"], "0.5 14.9 19.3": ["oligotrophic"], "14.7 19.9 9.2": ["spotfires"], "10.0 8.5 13.5": ["pyrites"], "8.4 20.7 23.9": ["pows"], "8.9 -2.0 8.6": ["longcourse"], "3.4 -0.1 10.6": ["faoi"], "13.2 18.4 10.9": ["jeebus"], "-3.2 5.7 6.7": ["dastar"], "0.7 6.5 -4.5": ["reate"], "5.0 10.7 11.6": ["ewsachse"], "0.0 3.5 10.4": ["shala"], "1.5 -6.4 10.8": ["consid"], "-1.9 26.9 1.9": ["indoctrinators"], "2.1 -0.2 -1.1": ["uis"], "18.1 6.8 16.3": ["hexacore"], "-2.8 17.2 6.4": ["epileptogenic"], "9.1 8.4 12.4": ["bett"], "4.0 6.7 8.2": ["importancia"], "14.0 4.7 -0.5": ["itssubsidiaries"], "8.3 15.5 20.8": ["northwestwards"], "7.0 4.0 10.0": ["alcune"], "0.5 13.1 6.0": ["reelectionists"], "12.4 5.1 9.8": ["crateloads"], "-1.2 6.8 -5.2": ["beiden"], "15.7 27.4 13.9": ["machette"], "12.0 -6.2 26.4": ["elotes"], "16.7 5.4 -5.0": ["powerbrands"], "9.8 13.1 3.3": ["multimonitor"], "10.6 2.8 5.1": ["webtv"], "9.2 15.5 6.3": ["femi"], "6.6 28.5 13.2": ["masteries"], "1.9 15.3 18.9": ["swampier"], "20.2 6.8 22.6": ["mussy"], "1.4 0.5 11.3": ["talkathons"], "-3.0 8.5 12.3": ["reinserts"], "20.7 -7.7 -3.1": ["neemt"], "23.3 3.8 21.2": ["schottische"], "9.5 14.3 -1.0": ["meto"], "7.1 -1.4 1.7": ["psychol"], "4.9 8.5 16.1": ["arraigment"], "11.7 -2.2 3.1": ["hyperstimulated"], "-2.3 10.7 0.5": ["isvery"], "5.9 8.3 19.9": ["weat"], "7.2 10.3 9.6": ["wearyingly"], "0.6 10.5 9.9": ["thenight"], "-2.9 18.4 -1.0": ["counterposing"], "13.9 9.0 12.0": ["betsy"], "4.2 2.5 12.7": ["roberto"], "7.1 4.5 14.4": ["tarpan"], "12.5 10.4 14.7": ["eponymously"], "3.0 25.5 20.4": ["vibrios"], "7.1 7.7 13.5": ["trigylcerides"], "15.8 4.8 19.2": ["restaruant"], "5.3 5.8 10.5": ["aspossible"], "8.7 1.9 13.2": ["jamaican"], "3.1 5.3 8.9": ["endocrinal"], "16.5 13.1 18.3": ["glooms"], "1.7 -1.1 0.3": ["nonmedically"], "-3.7 10.6 5.6": ["desrves"], "3.0 21.9 4.2": ["expiating"], "-0.5 6.8 18.0": ["tuwa"], "6.0 0.7 4.3": ["episodics"], "3.1 13.6 2.1": ["condemened"], "0.3 3.2 2.6": ["vasodilate"], "15.6 6.2 26.9": ["buttonwood"], "-3.1 -9.9 -5.2": ["selcted"], "4.3 -3.0 14.7": ["siguradong"], "17.4 16.7 13.6": ["crappily"], "6.5 4.9 -4.1": ["overally"], "0.4 -0.8 11.2": ["quelque"], "10.2 -0.6 17.1": ["taiwanese"], "1.9 1.6 3.7": ["twe"], "-2.6 10.2 1.1": ["abscondment"], "15.9 9.8 14.0": ["prepainted"], "0.2 12.7 20.6": ["homeopathically"], "17.0 9.3 16.2": ["toecap"], "-0.7 5.9 6.8": ["performanceand"], "9.2 10.4 12.8": ["feedzone"], "-7.3 7.4 5.4": ["amenorrhoea"], "2.7 3.0 0.8": ["interlockings"], "19.2 10.8 23.5": ["bouncies"], "-6.0 15.4 8.7": ["overplan"], "-8.0 -2.6 10.0": ["eams"], "17.5 37.0 7.1": ["boogiemen"], "13.2 11.6 17.9": ["rewelded"], "4.6 15.7 9.8": ["uncrosses"], "6.5 16.9 18.8": ["lwa"], "15.7 8.8 9.6": ["previewers"], "11.7 8.1 7.6": ["dualmode"], "20.3 10.3 33.1": ["jabiru"], "-6.2 3.1 14.9": ["tachi"], "18.1 1.3 15.3": ["drw"], "3.3 17.6 13.3": ["nonlinearly"], "0.2 16.1 3.6": ["monastry"], "0.6 -0.3 8.1": ["sangguniang"], "-3.4 -5.5 0.5": ["cirector"], "9.5 26.1 16.3": ["defuser"], "13.8 8.7 19.9": ["vaporetti"], "12.7 5.3 41.1": ["boletus"], "5.4 3.7 3.3": ["boxholders"], "-0.6 13.1 1.4": ["mision"], "3.8 2.6 5.2": ["backshells"], "-5.5 24.0 7.5": ["knuckledraggers"], "11.9 12.2 7.1": ["lujah"], "17.2 9.2 28.3": ["sauceless"], "2.8 8.5 0.1": ["nonmedia"], "6.0 17.0 1.6": ["doctype"], "10.1 8.1 13.1": ["reassortments"], "26.0 11.3 19.5": ["toodles"], "-3.0 23.2 7.6": ["rewarder"], "-1.9 11.0 6.7": ["parens"], "5.5 0.3 -6.4": ["nion"], "-4.3 14.5 -4.0": ["noncoaching"], "5.6 4.6 5.5": ["macroblock"], "13.8 2.5 -1.5": ["asubsidiary"], "-5.9 4.4 9.4": ["gameweeks"], "2.4 7.5 4.2": ["needsto"], "12.5 13.4 25.1": ["colchicums"], "9.3 4.5 35.0": ["guisado"], "12.3 19.7 3.1": ["remerging"], "7.9 12.0 5.3": ["facebooked"], "-0.4 -1.7 -3.0": ["bioprostheses"], "5.4 13.9 17.0": ["diesease"], "3.9 1.0 -0.0": ["oganisations"], "9.2 13.7 4.5": ["uncanniness"], "5.6 4.4 7.0": ["rhapsodises"], "1.8 11.8 28.0": ["flyfishers"], "13.5 13.2 9.3": ["technogeeks"], "20.0 32.3 15.4": ["norn"], "0.2 18.1 17.3": ["adamance"], "6.2 0.4 7.2": ["capit"], "4.3 6.5 8.5": ["zapin"], "12.5 9.2 4.1": ["uglified"], "16.5 9.9 24.8": ["maleo"], "-6.7 17.8 2.5": ["listend"], "3.7 1.2 9.2": ["biospherians"], "4.6 6.2 8.9": ["ethel"], "2.9 19.0 7.6": ["backwood"], "1.4 1.6 2.5": ["ambulanced"], "4.8 6.2 13.9": ["schoolbuilding"], "10.1 8.1 22.6": ["patination"], "10.8 13.7 8.7": ["bofors"], "8.7 -3.0 7.7": ["targed"], "22.7 3.6 30.5": ["maribou"], "8.8 12.3 10.5": ["newies"], "-1.8 2.5 0.5": ["chartership"], "-0.6 8.8 8.4": ["hurldes"], "-4.3 4.6 14.6": ["jada"], "11.7 15.2 10.0": ["nanocells"], "-3.2 -2.4 0.1": ["ohr"], "13.1 -1.7 26.0": ["plateware"], "4.3 0.2 -1.2": ["leuprorelin"], "6.6 13.4 5.9": ["lugubriousness"], "18.5 15.8 20.5": ["cockade"], "-5.8 7.9 6.1": ["myelomas"], "6.6 16.7 4.6": ["yaradua"], "8.1 -0.3 17.8": ["hotdogger"], "12.4 8.6 17.8": ["isabout"], "18.7 12.1 15.5": ["munks"], "11.6 6.6 8.2": ["agrin"], "19.9 -2.9 18.0": ["statuaries"], "9.3 15.1 7.9": ["streching"], "9.0 8.5 5.4": ["caracol"], "2.6 9.3 7.1": ["umno"], "7.6 6.4 28.4": ["trang"], "10.2 7.9 7.4": ["exif"], "0.1 3.0 14.9": ["feira"], "4.5 1.6 5.2": ["quadri"], "9.6 -4.6 10.6": ["stuh"], "-1.9 2.0 8.5": ["reprehenderit"], "11.7 7.8 0.5": ["mpge"], "2.9 2.6 -3.3": ["implented"], "9.2 4.0 11.4": ["nove"], "11.6 9.0 12.2": ["pasteurising"], "7.2 6.0 17.5": ["comienza"], "6.0 15.6 10.1": ["stitchwork"], "4.6 13.3 23.3": ["jimsonweed"], "10.8 5.4 8.1": ["poorish"], "24.0 12.9 33.6": ["stonelike"], "5.1 14.0 6.5": ["triump"], "16.4 3.3 35.2": ["dragees"], "1.7 13.5 7.7": ["spreadmarts"], "0.2 9.5 19.9": ["tattooers"], "12.1 -1.3 10.6": ["ratecard"], "10.3 3.6 4.0": ["openwheel"], "15.4 23.4 11.6": ["aeronauts"], "21.8 5.3 14.8": ["unwoven"], "13.2 4.6 15.5": ["bandhini"], "22.5 -4.8 8.5": ["homegoods"], "10.5 12.4 17.3": ["unticked"], "13.0 8.3 29.9": ["tatin"], "21.1 -5.7 15.1": ["undreds"], "9.3 5.3 37.3": ["flanken"], "1.0 7.2 7.3": ["postdisaster"], "3.2 3.0 4.1": ["preconcentration"], "18.9 18.7 34.3": ["radula"], "8.9 6.7 17.6": ["asupra"], "5.9 0.7 8.8": ["electromyogram"], "14.7 19.4 8.2": ["positionable"], "6.4 8.6 13.4": ["microvia"], "-0.9 8.8 13.7": ["rakh"], "8.9 2.1 22.2": ["cumberland"], "8.0 1.6 33.7": ["pescatore"], "1.3 7.4 4.2": ["anamorphically"], "6.2 2.0 2.7": ["photomultiplier"], "8.2 11.0 4.3": ["acknolwedged"], "11.1 6.6 6.6": ["midable"], "-2.0 -8.9 8.8": ["consu"], "13.6 19.9 12.1": ["calaboose"], "5.2 9.9 6.7": ["unraised"], "19.6 22.9 18.1": ["cahones"], "13.2 5.2 8.1": ["agbio"], "21.5 -3.9 14.4": ["agrifoods"], "-4.6 11.1 10.8": ["counterplan"], "1.8 10.8 13.2": ["khong"], "13.4 10.6 10.8": ["ballgoers"], "6.9 8.8 11.6": ["direcly"], "6.5 18.2 20.9": ["sluffing"], "7.7 5.1 4.4": ["miserablists"], "5.8 10.1 14.9": ["undereye"], "3.7 6.6 1.1": ["thegeneral"], "1.5 2.6 -7.9": ["ffice"], "0.5 -3.1 -3.7": ["wriiten"], "14.5 2.4 -2.4": ["technoloy"], "9.3 -5.0 24.9": ["campari"], "31.7 15.4 39.3": ["pumkin"], "5.1 7.4 5.6": ["dirve"], "0.8 26.5 4.0": ["legitimacies"], "0.2 21.4 11.1": ["sacraficed"], "11.8 -2.3 5.7": ["croissance"], "12.1 4.0 40.2": ["dolphinfish"], "9.9 3.0 8.6": ["derry"], "8.0 23.1 14.3": ["gettign"], "3.7 8.3 12.3": ["myeong"], "0.5 17.3 -3.4": ["retentionist"], "9.9 3.2 8.7": ["microkeratomes"], "2.7 14.0 14.7": ["artest"], "8.5 3.2 6.0": ["comptition"], "-1.4 1.6 4.8": ["horseperson"], "2.2 10.8 11.4": ["shycelticwitch"], "-0.4 0.1 7.4": ["mmcfed"], "6.2 -2.1 1.8": ["tenges"], "14.9 10.4 13.4": ["posied"], "18.4 9.5 23.7": ["paulownia"], "2.9 2.9 10.8": ["simone"], "6.4 30.1 3.8": ["harmad"], "2.2 20.4 -0.2": ["chauvinistically"], "12.6 -2.0 14.7": ["farmlet"], "13.1 25.3 19.0": ["outies"], "-11.3 3.8 4.5": ["noteworthiness"], "3.7 22.3 9.2": ["epiphenomena"], "13.0 7.4 42.1": ["koura"], "-1.7 -2.3 8.2": ["ived"], "12.2 7.0 19.5": ["preheaters"], "-11.6 0.8 6.2": ["selectivities"], "-10.1 -0.8 14.6": ["husban"], "16.3 25.3 4.7": ["supergun"], "5.5 7.2 11.6": ["beatless"], "13.0 -8.5 6.8": ["phar"], "5.6 7.8 1.3": ["macroeconomically"], "7.1 15.1 7.2": ["remobilised"], "10.0 11.4 13.3": ["hookie"], "-1.8 6.9 14.2": ["comng"], "9.4 15.6 25.2": ["flaxes"], "12.3 11.3 14.6": ["spoonerisms"], "-5.3 4.4 5.8": ["oblates"], "2.9 5.5 3.5": ["fronto"], "5.5 9.9 15.6": ["auberges"], "9.9 5.3 12.1": ["uge"], "-3.7 16.8 7.3": ["cystatin"], "21.7 4.1 35.3": ["bowlfuls"], "8.4 -0.5 30.7": ["bruschette"], "7.4 16.1 11.3": ["profer"], "13.6 13.9 15.5": ["payal"], "-5.0 9.6 7.5": ["jeden"], "-6.1 2.5 9.2": ["radicular"], "9.5 6.3 6.3": ["controvesial"], "8.9 7.4 27.3": ["kapitan"], "5.5 3.0 10.0": ["handin"], "7.3 7.7 11.7": ["ontinue"], "-3.3 15.9 7.3": ["frends"], "7.5 7.7 12.1": ["paleochannels"], "6.4 2.7 3.6": ["processo"], "10.1 1.1 4.8": ["motelling"], "5.7 -7.1 4.4": ["dichloroacetate"], "5.0 13.6 17.0": ["swick"], "1.5 4.1 15.6": ["peridotites"], "2.0 7.4 5.6": ["vfs"], "-0.3 -0.1 8.0": ["eem"], "1.5 11.6 5.9": ["communards"], "9.9 7.0 19.1": ["sporters"], "15.1 10.0 9.4": ["textboxes"], "4.8 -0.8 6.8": ["glyconutrient"], "12.6 16.6 12.9": ["maidenly"], "17.7 4.6 10.0": ["doubleshot"], "1.4 12.3 14.4": ["horatio"], "4.2 12.8 9.2": ["apercus"], "9.2 16.9 28.2": ["depredating"], "6.9 14.9 25.0": ["kahi"], "10.0 13.8 8.8": ["designedly"], "3.3 2.5 2.5": ["formaldehydes"], "19.0 8.3 31.1": ["purpley"], "-6.0 -11.1 8.9": ["experien"], "18.7 9.9 27.4": ["coffeeberry"], "8.7 25.1 5.9": ["consuetude"], "2.8 -2.5 8.2": ["rty"], "0.5 11.1 3.8": ["karthik"], "10.4 6.6 12.3": ["tupac"], "-4.7 4.9 2.5": ["sesamoiditis"], "8.8 -0.7 22.2": ["corsetted"], "-0.1 2.4 4.4": ["whow"], "5.0 10.2 19.6": ["kitne"], "2.7 10.3 5.5": ["nonspecifically"], "12.5 9.4 15.0": ["centreing"], "5.2 1.3 5.1": ["nonluxury"], "6.7 17.9 7.4": ["namazis"], "17.6 14.4 9.9": ["triopoly"], "18.3 6.0 15.3": ["wotsit"], "13.8 5.5 5.9": ["geotechnics"], "7.7 28.7 1.5": ["waterboards"], "5.1 14.1 7.5": ["makesure"], "4.3 15.6 3.5": ["morphic"], "9.2 16.1 9.1": ["cras"], "7.5 10.3 9.1": ["coolheadedness"], "8.6 8.2 15.2": ["rando"], "5.3 7.1 7.0": ["inkpot"], "13.1 8.2 -0.8": ["foulups"], "12.3 13.2 12.6": ["starquakes"], "14.5 6.6 13.9": ["naphta"], "7.2 3.4 -4.8": ["vioxx"], "4.0 9.6 18.2": ["tribendimidine"], "-4.6 13.7 -0.3": ["revictimizing"], "12.9 21.4 13.3": ["isjust"], "0.6 15.2 13.2": ["stablility"], "26.3 26.1 13.7": ["pulverises"], "9.7 14.2 4.7": ["webcamera"], "8.4 4.1 -3.3": ["multislice"], "0.5 22.1 -1.7": ["immidiate"], "3.3 9.2 -6.4": ["believs"], "11.6 17.5 21.4": ["footbinding"], "6.4 1.5 18.0": ["refreshements"], "1.5 12.5 3.4": ["genizah"], "2.5 -7.3 3.4": ["bioseparations"], "-0.5 13.7 10.4": ["kurstaki"], "11.4 26.4 3.4": ["spited"], "3.9 12.7 15.8": ["reng"], "2.1 6.9 -5.2": ["trichostatin"], "8.8 3.7 0.9": ["outfor"], "5.3 10.5 13.6": ["nanostructural"], "-3.1 -5.3 6.1": ["olli"], "1.7 7.1 8.1": ["subtitute"], "-3.8 9.3 12.8": ["lamprophyre"], "15.3 12.1 9.6": ["ithout"], "14.5 1.8 8.0": ["trashtastic"], "4.0 10.0 10.0": ["layton"], "12.4 17.7 -0.0": ["comandeered"], "-4.6 2.1 0.1": ["tulkus"], "4.4 13.7 5.2": ["socity"], "5.6 8.6 14.9": ["noen"], "14.4 6.0 7.8": ["unspecificed"], "8.6 10.7 9.7": ["thumbnailed"], "9.6 19.0 11.1": ["overanalyzes"], "10.3 15.2 17.5": ["margarito"], "-3.8 -1.2 9.5": ["elementry"], "10.6 9.9 17.5": ["vees"], "9.7 2.5 8.1": ["legen"], "-6.2 5.3 7.5": ["middleschool"], "-2.9 3.1 13.1": ["seudah"], "1.7 13.6 0.6": ["ftopia"], "15.1 13.1 28.1": ["naupaka"], "3.5 3.7 0.6": ["byan"], "-2.3 26.0 1.0": ["musharraf"], "12.3 11.8 9.5": ["illustriously"], "-2.7 8.5 15.6": ["natalo"], "-6.8 -2.2 -0.3": ["semesterisation"], "3.7 5.4 16.3": ["requi"], "6.4 32.7 1.4": ["deterence"], "-4.2 21.9 6.6": ["unhabitable"], "8.1 8.9 15.0": ["slowburn"], "6.7 6.4 11.3": ["platz"], "9.5 6.1 16.7": ["realidad"], "8.7 11.8 5.8": ["alphanumerics"], "11.3 2.8 11.3": ["onground"], "15.3 11.8 5.2": ["phonecam"], "1.5 1.1 2.6": ["ature"], "0.2 9.8 12.2": ["acanthite"], "8.9 -0.5 0.6": ["dfs"], "5.7 16.9 8.7": ["superlegislature"], "6.1 12.2 2.5": ["outcasted"], "6.0 22.1 19.2": ["overhands"], "5.7 8.7 9.2": ["pointscorers"], "-1.5 13.5 7.0": ["anonmyity"], "12.7 9.9 18.2": ["warehousers"], "5.1 -0.8 -4.2": ["powerchair"], "15.0 15.6 13.0": ["amazements"], "5.3 14.2 13.3": ["larboard"], "10.2 6.1 14.7": ["transplanters"], "8.5 24.6 10.0": ["counterchallenge"], "6.6 -2.6 7.5": ["vtiger"], "13.9 29.3 2.2": ["nucler"], "3.6 11.8 14.2": ["retiredgustav"], "14.6 12.8 0.9": ["governmentand"], "1.6 6.3 11.0": ["milia"], "3.6 2.3 15.2": ["tracey"], "6.4 6.2 20.2": ["cecal"], "22.4 11.3 13.5": ["coverer"], "5.0 -2.6 15.0": ["centrino"], "2.8 -6.1 -4.3": ["entra"], "11.4 2.0 13.5": ["jamdani"], "4.8 9.5 8.5": ["stefan"], "21.9 11.5 16.6": ["pullies"], "24.9 4.4 20.3": ["paternoster"], "9.8 11.2 19.0": ["prestine"], "-4.7 14.4 9.6": ["tahara"], "9.9 11.7 5.2": ["pires"], "-0.2 3.6 6.0": ["dition"], "18.6 27.6 13.4": ["robocops"], "8.4 9.3 9.5": ["recht"], "9.4 9.9 7.5": ["subprocesses"], "-2.6 5.3 6.0": ["epsiodes"], "4.7 4.3 4.2": ["stomatology"], "-0.8 7.2 7.2": ["prostitutions"], "8.0 -3.8 19.0": ["cora"], "-0.9 22.0 -5.5": ["misruling"], "3.6 15.7 15.2": ["rivera"], "12.1 9.6 12.1": ["blethering"], "12.9 13.0 24.6": ["cistus"], "9.9 11.4 19.4": ["granda"], "12.8 6.3 40.4": ["ossobuco"], "5.6 -1.3 10.0": ["effe"], "12.4 18.1 21.4": ["slinged"], "20.9 21.6 14.2": ["noosphere"], "-0.9 5.3 3.4": ["wath"], "6.9 16.1 9.5": ["reallity"], "20.8 12.4 10.4": ["tsunamic"], "-1.9 8.8 6.2": ["anterograde"], "3.8 16.4 -2.6": ["buhari"], "8.4 -5.5 2.0": ["bks"], "3.1 4.0 2.8": ["degasser"], "-8.0 22.5 10.8": ["hospitalman"], "7.0 11.4 10.4": ["lightwelter"], "4.6 10.1 11.3": ["amentities"], "4.2 14.7 -4.3": ["obscurer"], "13.4 3.3 0.7": ["suitablility"], "7.4 13.1 12.2": ["cincy"], "1.9 4.2 4.7": ["molindone"], "0.0 7.8 6.6": ["withthis"], "4.3 18.7 19.3": ["naggers"], "9.1 3.5 1.1": ["connu"], "5.5 14.6 4.5": ["autodetect"], "8.0 1.5 4.6": ["moonlighter"], "13.9 6.0 10.0": ["totalmente"], "1.0 -2.6 16.9": ["gigaliters"], "-4.4 4.4 5.1": ["rehypothecation"], "4.7 7.0 12.6": ["katika"], "19.9 13.1 4.7": ["aerofoils"], "8.0 7.3 6.1": ["voluptua"], "15.2 9.9 14.5": ["chicka"], "13.6 12.3 1.6": ["scotoma"], "10.5 2.8 7.0": ["laso"], "12.3 3.7 10.7": ["competiti"], "-3.0 13.7 3.9": ["discours"], "8.2 11.8 4.6": ["resensitize"], "-3.8 3.9 2.2": ["singleseason"], "10.8 10.3 27.5": ["oarlocks"], "-0.1 6.5 14.1": ["kamnans"], "-1.1 5.5 12.2": ["mapa"], "-2.6 2.5 12.4": ["ibig"], "-1.9 5.0 9.0": ["uricase"], "16.7 17.0 10.4": ["crushin"], "5.8 26.0 11.3": ["ambiguousness"], "-2.0 1.0 9.4": ["nigam"], "1.6 -0.4 9.2": ["tendance"], "19.5 -0.3 1.5": ["prewiring"], "4.6 3.2 9.5": ["kuin"], "24.9 1.3 10.9": ["helios"], "2.2 8.9 12.3": ["mondegreens"], "7.5 9.2 -6.0": ["coloumn"], "20.0 14.0 19.0": ["spatulae"], "27.6 7.6 5.7": ["lapboard"], "16.2 10.5 4.4": ["suburbanisation"], "5.3 8.5 9.7": ["niko"], "11.5 15.2 11.7": ["watermakers"], "8.6 1.5 -8.0": ["indeveloping"], "4.9 12.6 8.0": ["communters"], "11.8 14.2 8.1": ["spinons"], "10.6 5.6 27.9": ["benne"], "8.2 20.1 9.0": ["englishman"], "8.0 9.5 29.7": ["naped"], "4.8 18.4 13.9": ["songlines"], "22.4 18.5 20.3": ["clerestories"], "18.1 26.0 20.2": ["otakus"], "17.2 -5.9 13.7": ["rueda"], "21.6 12.0 22.3": ["cankle"], "19.6 4.8 17.6": ["passersbys"], "0.7 1.1 5.7": ["ssn"], "14.0 14.3 6.3": ["itcan"], "10.8 14.0 1.5": ["vitalizes"], "20.3 4.8 3.0": ["restyles"], "6.5 16.5 21.2": ["kongo"], "9.1 1.1 14.1": ["freud"], "11.3 13.5 9.1": ["fane"], "7.0 7.0 3.5": ["bies"], "7.1 4.4 9.4": ["whoppingly"], "-5.2 -2.6 2.2": ["photopheresis"], "5.1 -2.1 16.1": ["longyis"], "6.2 1.5 17.1": ["paida"], "8.1 12.3 14.6": ["condyles"], "10.9 6.1 10.3": ["uhhhhh"], "6.3 9.6 -1.7": ["undersecured"], "1.1 6.1 -0.4": ["reauthorised"], "12.3 8.2 15.1": ["mcmahon"], "16.7 17.5 8.8": ["cark"], "-3.3 0.9 -2.2": ["reportability"], "13.1 29.4 13.8": ["batarangs"], "-3.7 9.9 8.0": ["fricative"], "6.6 4.3 6.7": ["levaquin"], "4.2 1.9 13.1": ["jkm"], "8.7 8.6 19.4": ["daks"], "14.8 15.7 8.2": ["plogg"], "7.3 19.0 19.5": ["loki"], "9.7 2.7 4.5": ["tamburitza"], "20.8 9.7 19.1": ["froghopper"], "-2.1 19.8 5.8": ["communio"], "21.0 2.6 10.0": ["minimajor"], "11.0 0.9 2.0": ["interlinings"], "0.8 8.5 13.2": ["shttp"], "6.9 7.4 4.5": ["derbi"], "6.2 1.3 6.1": ["luhr"], "2.3 14.6 1.9": ["masculinizing"], "8.9 14.0 0.2": ["conquesting"], "20.8 16.1 10.9": ["cauterising"], "9.8 19.0 39.1": ["hardwater"], "11.2 19.6 15.6": ["mutancy"], "23.0 24.7 17.0": ["robocop"], "11.3 3.0 14.4": ["ringlike"], "16.7 2.7 16.2": ["mixie"], "2.2 0.9 16.3": ["paleobiologists"], "19.0 11.9 40.6": ["leadhead"], "4.7 6.7 29.4": ["shorba"], "8.7 4.5 13.1": ["palabas"], "13.2 13.9 9.2": ["planemos"], "9.0 6.1 -0.4": ["novelisations"], "6.7 12.2 12.7": ["euthenized"], "9.2 10.7 -2.9": ["wityh"], "7.2 6.2 10.8": ["sorpresa"], "19.0 10.4 29.8": ["porkiness"], "2.2 4.7 1.9": ["kabrastan"], "-2.3 8.7 3.0": ["lapbelt"], "1.5 5.1 6.4": ["chakkajam"], "7.2 0.8 14.1": ["voo"], "2.1 4.4 14.3": ["gwybod"], "2.7 11.5 9.1": ["glycated"], "3.6 6.6 10.5": ["twerpy"], "9.6 9.5 15.2": ["butanone"], "-0.4 -0.5 0.4": ["bsc"], "-1.2 1.0 10.4": ["operatin"], "-9.1 0.2 -9.4": ["cadidates"], "3.9 13.8 4.6": ["unpublish"], "16.5 19.3 20.9": ["genet"], "11.0 9.6 14.6": ["purveyance"], "11.0 18.1 3.8": ["theiving"], "-3.0 20.0 -1.6": ["factionally"], "7.1 19.3 4.8": ["arogant"], "7.3 20.4 2.9": ["keeing"], "6.7 11.5 5.1": ["montbkk"], "15.7 8.6 23.0": ["haybales"], "6.6 13.6 6.4": ["whoremongers"], "5.8 18.7 12.8": ["kratos"], "6.0 28.0 15.2": ["sovreignty"], "-6.8 24.4 1.5": ["analize"], "4.5 21.5 2.0": ["orginizations"], "17.2 12.1 30.9": ["santolina"], "19.1 6.2 20.7": ["porkpie"], "9.7 10.4 23.0": ["pule"], "1.7 12.7 13.3": ["bway"], "-1.2 13.3 -5.1": ["expellee"], "9.2 14.6 5.1": ["hecould"], "21.1 18.7 10.7": ["joost"], "12.5 9.6 21.2": ["translucently"], "7.4 4.1 10.7": ["orthodics"], "4.6 7.2 4.1": ["marcia"], "4.1 5.3 6.0": ["impermissable"], "11.0 -2.0 9.4": ["seks"], "8.4 25.6 10.9": ["idolatries"], "2.2 7.0 9.6": ["enzootic"], "21.4 8.4 13.5": ["superchip"], "5.5 14.5 7.6": ["formalisms"], "9.0 8.5 -3.5": ["nonpower"], "4.6 4.3 17.9": ["westcentral"], "3.1 6.5 5.9": ["etribes"], "11.3 1.7 10.4": ["spiritus"], "16.0 10.2 9.5": ["pickens"], "12.0 7.6 24.6": ["hawkmoths"], "6.9 8.5 6.9": ["internatioanl"], "-1.0 2.6 11.4": ["orgo"], "14.0 2.7 19.2": ["tyra"], "7.7 2.2 3.6": ["bthe"], "7.4 16.3 15.4": ["pneumocystis"], "4.7 3.7 8.3": ["pentathlons"], "17.7 8.7 30.9": ["falooda"], "-1.2 0.2 2.6": ["univs"], "0.8 -0.0 -0.6": ["quently"], "19.2 13.4 22.0": ["tuckus"], "12.0 20.8 16.9": ["teko"], "2.0 1.8 10.7": ["brans"], "13.9 2.6 15.5": ["streetkids"], "20.8 13.8 11.1": ["shakable"], "1.0 11.6 4.8": ["policer"], "13.8 16.1 12.1": ["bering"], "-3.4 2.1 13.1": ["superlevy"], "0.8 8.3 13.3": ["gutom"], "-11.4 7.6 12.7": ["shalls"], "2.0 2.9 6.6": ["bandcamp"], "1.0 12.1 -6.4": ["premeir"], "-1.2 6.0 7.5": ["isoprostane"], "5.8 6.4 6.6": ["sechs"], "-0.2 26.5 8.0": ["answere"], "2.8 6.5 18.4": ["blendings"], "25.9 8.1 -1.1": ["compant"], "1.1 4.4 7.9": ["abierto"], "13.9 14.6 11.5": ["tracheae"], "1.3 15.5 6.8": ["deeprooted"], "5.5 1.0 3.7": ["spn"], "-1.1 12.7 14.0": ["ingon"], "4.9 14.4 12.1": ["unamendable"], "7.6 25.2 5.7": ["regardles"], "3.0 13.1 16.4": ["serendipities"], "-0.8 -7.5 4.2": ["evenue"], "-4.9 -5.9 -0.5": ["wald"], "13.5 21.6 1.6": ["crashlands"], "17.7 11.0 10.0": ["reving"], "-12.5 8.0 -4.1": ["appointable"], "4.8 4.9 13.9": ["voluteers"], "20.3 19.0 14.4": ["noosed"], "10.0 21.8 10.0": ["hosereel"], "16.7 2.8 -9.3": ["revolutionalized"], "-1.1 9.2 8.3": ["isomeric"], "-0.6 2.8 6.6": ["efect"], "19.7 -0.1 13.1": ["longlife"], "4.2 7.7 12.1": ["iwan"], "9.9 8.1 14.2": ["speedcubers"], "6.9 -3.6 6.9": ["orthoxylene"], "11.1 19.9 5.9": ["fireys"], "1.0 12.7 9.4": ["playo"], "9.9 5.1 5.5": ["rumourtrage"], "10.4 1.1 4.4": ["nonregistration"], "9.2 11.9 11.4": ["frend"], "26.2 6.0 -0.5": ["holographics"], "7.9 28.8 10.4": ["neoconservativism"], "20.7 12.7 21.6": ["rubbly"], "-0.0 6.4 3.6": ["dikha"], "10.9 5.3 30.6": ["flycasting"], "8.5 13.8 14.8": ["mylonite"], "0.9 24.6 13.8": ["exagerate"], "20.3 3.5 11.7": ["victrola"], "0.8 7.4 4.6": ["harumphed"], "1.0 8.7 9.1": ["coachin"], "11.0 24.5 -3.8": ["boming"], "11.2 18.6 7.6": ["whipcrack"], "9.2 3.0 12.1": ["seb"], "11.9 8.9 16.2": ["crevassed"], "5.4 13.4 17.2": ["unhe"], "2.7 18.8 16.4": ["hurr"], "4.3 9.4 7.9": ["paradichlorobenzene"], "11.5 16.8 12.5": ["petroliferous"], "4.6 21.0 6.7": ["monent"], "10.5 18.0 7.7": ["unfortunetly"], "5.1 8.7 9.6": ["personalizations"], "16.0 10.2 20.8": ["stratums"], "5.3 6.0 17.5": ["sulphoraphane"], "9.5 2.3 12.0": ["henleys"], "7.8 0.8 2.6": ["rof"], "8.5 7.6 6.6": ["investisseurs"], "5.1 12.6 11.7": ["subdisciplines"], "-1.9 5.8 -2.1": ["outlegged"], "4.1 5.8 5.4": ["ient"], "9.8 12.5 5.0": ["acctually"], "5.5 6.2 12.7": ["ginagamit"], "8.5 22.5 9.6": ["outshouting"], "16.6 15.4 22.2": ["stickpins"], "-10.0 15.8 -2.5": ["proselyting"], "13.3 11.5 11.2": ["unplaceable"], "-3.8 18.0 5.3": ["rescript"], "10.6 7.6 10.1": ["kabadi"], "0.4 23.9 4.1": ["sayyed"], "-5.7 2.5 -4.4": ["exce"], "-1.4 9.0 0.1": ["reenforces"], "17.6 2.5 30.7": ["conodonts"], "3.8 12.9 5.4": ["glamours"], "20.2 3.8 11.6": ["boneshaker"], "6.9 -2.2 13.7": ["miniconcert"], "13.8 2.5 11.1": ["cutterbar"], "8.7 2.2 8.7": ["interspinous"], "16.3 21.0 36.1": ["snailfish"], "7.2 11.1 0.4": ["alten"], "11.1 15.1 29.8": ["aoli"], "5.7 5.8 8.3": ["firestopping"], "2.5 8.9 2.3": ["listners"], "7.6 8.0 3.8": ["snippits"], "4.9 12.5 10.8": ["sathe"], "17.6 3.6 11.2": ["shekere"], "0.1 13.9 3.8": ["doorknocks"], "11.3 8.8 9.9": ["sydrome"], "8.4 -8.2 8.6": ["accordi"], "-2.9 14.1 7.4": ["tarawih"], "10.6 19.0 0.6": ["msut"], "14.5 16.2 18.0": ["stilting"], "-5.0 23.1 9.1": ["humilty"], "7.6 6.8 -2.9": ["affil"], "24.9 21.2 21.5": ["trackhoes"], "7.9 1.4 9.5": ["vielle"], "11.0 6.3 0.6": ["analysist"], "9.3 1.0 6.7": ["ecoconscious"], "2.4 6.0 0.5": ["internationalen"], "5.1 -4.6 5.0": ["atits"], "2.3 8.0 4.6": ["thermosensitive"], "3.0 -0.7 8.4": ["bandhgalas"], "10.4 6.1 14.0": ["gidda"], "11.9 9.0 11.5": ["jalousies"], "1.3 27.8 9.1": ["ghairat"], "4.2 24.0 9.9": ["interpenetrate"], "-1.2 -5.4 11.0": ["bookfest"], "7.5 3.4 7.2": ["subpoints"], "4.8 -2.7 3.0": ["bts"], "16.7 13.5 27.6": ["pinnate"], "7.3 30.5 7.0": ["heimat"], "1.1 12.8 6.3": ["bipolarism"], "-0.4 15.9 3.1": ["conserative"], "2.0 1.4 16.8": ["ngu"], "8.2 -2.7 2.7": ["monthsof"], "6.9 7.0 7.1": ["underwraps"], "1.3 6.8 6.9": ["chld"], "11.3 -0.2 13.0": ["quicksteps"], "-3.1 10.4 15.7": ["overburdensome"], "9.9 4.3 -6.0": ["theashes"], "3.0 13.6 9.6": ["parasitosis"], "7.1 -1.0 27.0": ["eddoes"], "27.1 4.6 -1.2": ["automator"], "-0.0 -4.0 4.6": ["whatson"], "13.1 7.7 31.1": ["krathongs"], "0.5 6.4 3.0": ["dinko"], "1.6 21.9 8.4": ["incommensurability"], "4.9 12.8 11.4": ["chiefest"], "10.0 17.3 10.9": ["juba"], "9.3 14.7 11.9": ["cavitations"], "3.9 4.2 10.2": ["thermogram"], "8.9 1.5 8.2": ["sizzlingly"], "2.1 10.0 11.3": ["radian"], "5.9 1.2 19.2": ["phong"], "6.1 11.7 17.7": ["ghos"], "11.5 2.4 4.1": ["devraient"], "12.9 14.9 5.0": ["biofield"], "10.7 2.7 26.7": ["outrigging"], "3.2 16.8 7.3": ["faute"], "2.6 7.2 6.2": ["microbolometers"], "-1.9 13.4 10.8": ["discombobulates"], "4.4 7.5 9.4": ["cruciates"], "11.8 4.4 14.6": ["tbp"], "-0.8 16.7 5.7": ["unresponded"], "24.4 17.1 18.7": ["apsaras"], "18.6 12.3 4.4": ["gudiya"], "4.3 20.3 13.7": ["verything"], "12.6 2.1 20.3": ["vod"], "6.5 8.7 8.8": ["polymersomes"], "4.8 -0.7 28.3": ["hatchability"], "6.0 3.6 8.4": ["ventolin"], "4.6 10.9 0.8": ["smi"], "2.7 4.4 8.3": ["eegoes"], "-3.6 5.7 -10.9": ["regading"], "12.3 9.5 1.3": ["nanotools"], "11.5 7.4 33.6": ["kakanin"], "5.0 0.4 -3.8": ["forsale"], "-1.2 -1.0 5.2": ["gratitudes"], "-0.6 13.1 9.3": ["shpiel"], "8.4 3.0 35.5": ["rotti"], "15.1 12.2 17.9": ["legge"], "2.5 -0.1 10.4": ["highweights"], "15.9 20.2 16.6": ["fuggedaboudit"], "5.6 5.6 -2.7": ["peptidic"], "2.8 11.0 11.7": ["lennox"], "5.2 5.7 12.8": ["enterobacteriaceae"], "3.6 8.9 26.3": ["pilon"], "9.1 10.2 21.4": ["wifeless"], "10.5 -3.8 16.7": ["bonues"], "0.5 13.7 10.5": ["grayson"], "5.8 10.1 0.8": ["dnata"], "11.1 26.4 17.2": ["sensibleness"], "6.6 0.9 2.5": ["ultraformer"], "0.3 7.9 -0.4": ["premillennial"], "4.8 8.0 31.2": ["taku"], "11.3 23.9 5.0": ["undauntedly"], "18.5 19.6 11.6": ["hussar"], "9.3 15.2 -1.2": ["pver"], "20.3 24.1 20.4": ["gibs"], "5.6 6.7 20.1": ["mutualisms"], "-1.1 18.9 0.3": ["fireable"], "10.6 11.3 11.1": ["liks"], "8.3 10.2 12.9": ["salares"], "0.1 6.9 0.0": ["bridger"], "4.8 -0.3 4.7": ["broncho"], "11.0 28.5 14.4": ["craphole"], "16.0 23.3 9.3": ["asskicking"], "6.3 10.0 17.4": ["rangel"], "1.7 6.8 7.1": ["medida"], "3.0 0.9 17.3": ["natu"], "-8.3 -4.2 1.2": ["psychometrist"], "-12.6 -6.7 1.4": ["eighthgrader"], "0.5 2.1 7.4": ["hern"], "13.8 -2.7 21.9": ["reweighed"], "1.9 12.7 9.0": ["santhara"], "15.4 9.6 12.7": ["boilersuits"], "3.3 15.7 19.0": ["tanta"], "8.5 14.3 6.8": ["wherethey"], "4.2 4.7 12.4": ["anded"], "-5.6 8.9 3.6": ["yppp"], "27.1 13.0 44.2": ["blenny"], "8.6 15.4 24.7": ["bushi"], "5.5 9.0 9.3": ["wavetable"], "4.7 7.9 10.2": ["discommoded"], "9.2 5.7 33.2": ["capicolla"], "15.8 7.9 19.0": ["beetled"], "-2.0 14.3 4.6": ["majoirty"], "15.0 3.6 15.3": ["celebu"], "8.0 4.2 6.9": ["brillante"], "0.9 1.2 12.3": ["connectorization"], "-3.4 8.6 10.6": ["noncanonical"], "4.2 16.8 9.8": ["stereotypy"], "-1.4 -0.4 3.1": ["coupl"], "-0.5 9.9 17.3": ["jok"], "12.5 12.7 13.5": ["playfighting"], "12.8 2.3 19.9": ["vocoded"], "8.1 16.1 22.3": ["cunningham"], "21.3 12.8 20.2": ["sandblasts"], "5.1 -1.1 5.8": ["judg"], "1.7 14.2 16.6": ["sempai"], "0.2 11.4 12.9": ["ticketmates"], "3.3 24.3 2.7": ["hyperbolizing"], "-0.6 -0.2 1.4": ["transcipt"], "21.9 25.8 37.1": ["gladius"], "0.6 -0.3 -3.9": ["titrator"], "10.1 10.7 12.6": ["dancerly"], "13.2 6.4 16.1": ["resuspend"], "6.5 12.1 18.2": ["dechlorinated"], "8.9 4.4 17.6": ["spirituous"], "11.1 2.4 12.4": ["unitizing"], "12.7 14.8 18.6": ["neckbeard"], "10.3 -4.1 12.2": ["fiberline"], "1.6 -1.5 14.6": ["iodisation"], "6.6 -4.0 23.2": ["cutflower"], "3.3 18.0 -0.9": ["amny"], "2.3 29.6 7.2": ["perpetrations"], "14.2 18.1 15.7": ["hunderds"], "9.2 8.6 13.9": ["parison"], "18.6 11.1 8.8": ["millionnaire"], "-1.6 8.9 1.5": ["lary"], "-8.9 25.4 -0.5": ["compartmentation"], "-2.0 1.9 3.7": ["vila"], "16.7 -6.8 7.6": ["infocomms"], "2.4 7.2 10.8": ["dekhe"], "12.0 15.4 8.2": ["websearch"], "8.8 15.5 -0.9": ["servient"], "-4.5 9.2 -3.5": ["joinees"], "11.7 2.1 2.9": ["sicher"], "2.6 4.1 7.2": ["chers"], "9.2 -6.7 1.4": ["nvestment"], "8.3 -1.8 26.9": ["braaied"], "11.4 8.8 20.1": ["youngun"], "6.9 -1.1 9.6": ["telenet"], "-0.4 -7.3 8.0": ["caa"], "15.5 12.2 19.8": ["garra"], "5.1 3.8 8.6": ["twinax"], "6.8 15.0 17.0": ["alleycat"], "15.7 -1.7 6.2": ["exising"], "20.2 0.5 6.1": ["yodellers"], "6.7 11.2 1.4": ["bureacrat"], "5.0 4.5 9.8": ["streeters"], "8.9 19.3 5.6": ["civitas"], "12.4 23.6 11.1": ["loather"], "18.6 11.3 9.0": ["refiller"], "-0.7 8.8 7.7": ["disbenefits"], "-0.1 7.0 -2.5": ["reocrd"], "9.1 11.0 22.2": ["acitivites"], "5.7 1.9 12.8": ["gyne"], "18.0 12.2 14.3": ["peepul"], "6.2 15.5 13.1": ["kitschiness"], "3.4 2.5 12.2": ["fous"], "-1.1 7.9 -6.0": ["transtion"], "6.6 8.0 8.4": ["xiaokang"], "3.4 13.0 30.5": ["dagat"], "3.5 10.2 13.5": ["nonallergic"], "22.1 8.7 15.4": ["celco"], "6.9 9.6 6.2": ["deathrow"], "13.9 10.2 20.9": ["manilla"], "0.9 8.6 1.3": ["rewriters"], "11.4 8.1 13.5": ["bittersweetly"], "9.7 3.1 15.6": ["spraypark"], "0.3 -1.3 12.1": ["cuarto"], "10.6 10.8 2.5": ["photoelectrochemical"], "-4.0 18.0 1.7": ["standardbearers"], "16.7 9.5 9.3": ["giz"], "8.0 4.5 -9.1": ["classfied"], "12.4 12.9 16.9": ["barbary"], "16.1 -1.9 12.8": ["wikitorial"], "1.5 4.0 11.2": ["wellplaced"], "-6.1 3.8 -6.2": ["acknowedged"], "7.5 4.2 12.5": ["noticia"], "11.1 16.7 7.9": ["monocracy"], "4.1 3.8 2.8": ["theirrespective"], "16.1 3.8 10.6": ["groundcare"], "5.8 20.9 13.9": ["unnessary"], "9.7 4.9 -3.4": ["areeba"], "0.3 8.2 5.9": ["masticatory"], "10.3 11.8 14.1": ["hoked"], "6.3 -7.2 14.1": ["stearin"], "22.2 14.8 15.6": ["catflap"], "22.4 17.4 9.2": ["sokaiya"], "12.4 4.2 10.7": ["accesibility"], "-0.1 3.0 13.7": ["favo"], "13.2 21.2 22.3": ["mosher"], "11.2 9.1 3.7": ["engineeer"], "13.1 7.3 2.2": ["cng"], "5.7 3.8 12.2": ["seconda"], "5.2 8.1 34.5": ["polpette"], "13.5 6.1 2.8": ["nside"], "8.7 19.4 10.9": ["spurtability"], "1.5 16.0 10.4": ["actory"], "-8.8 19.5 -3.2": ["importent"], "10.9 24.4 13.8": ["orisha"], "5.1 3.0 1.7": ["noncoronary"], "6.8 12.1 2.8": ["intonated"], "12.6 -0.1 2.2": ["tankfuls"], "2.7 19.2 13.0": ["alexia"], "1.9 14.8 9.6": ["microcantilevers"], "11.5 8.8 17.6": ["ruben"], "5.0 3.1 14.7": ["infanthood"], "3.0 -3.5 8.7": ["vedette"], "26.4 7.2 26.9": ["sheened"], "4.7 7.8 15.3": ["versace"], "-1.7 15.2 3.6": ["mahasabha"], "9.6 8.4 8.9": ["deacetylase"], "2.4 29.7 8.4": ["inkspots"], "13.7 3.3 24.9": ["plisse"], "-1.9 9.6 14.6": ["firematic"], "6.2 -0.2 4.7": ["unds"], "8.8 9.8 6.6": ["implementational"], "7.7 13.8 16.9": ["unbirthday"], "14.5 25.8 5.4": ["unleasing"], "10.6 2.0 2.1": ["zegt"], "20.9 17.6 31.7": ["waterweed"], "4.9 8.6 5.4": ["smogged"], "-4.7 0.7 9.1": ["multireedist"], "24.7 8.3 11.9": ["sunvisors"], "8.1 8.2 19.1": ["banga"], "1.9 5.4 11.9": ["versary"], "8.6 9.8 15.7": ["collagraph"], "-5.0 7.9 9.5": ["repegging"], "17.7 13.3 15.5": ["wodges"], "5.6 4.3 6.4": ["guiltys"], "2.6 -0.2 -3.2": ["recompensation"], "9.1 12.6 18.2": ["sweetrevenge"], "9.6 0.3 10.8": ["filiale"], "1.6 21.0 10.7": ["brainlock"], "-3.0 11.8 5.4": ["dominante"], "14.6 3.6 9.7": ["gril"], "22.0 6.3 28.1": ["silkies"], "10.7 16.5 36.7": ["nutmeats"], "15.0 8.1 11.7": ["advertisng"], "9.6 13.6 21.1": ["replikin"], "-5.9 2.7 1.6": ["homestudy"], "23.0 12.9 19.6": ["beermat"], "1.0 8.0 1.5": ["hightly"], "5.6 13.3 8.9": ["lungpower"], "9.9 22.5 8.0": ["princedom"], "17.5 17.2 27.7": ["auklet"], "9.5 4.8 14.2": ["lut"], "-3.6 6.3 -4.7": ["noncandidacy"], "3.0 6.4 10.3": ["blockmates"], "6.0 8.3 3.9": ["architectonics"], "5.9 -11.3 3.6": ["krwg"], "11.2 2.0 6.4": ["minifestival"], "9.0 14.0 13.9": ["megazooms"], "-3.2 3.5 11.6": ["homecall"], "3.6 15.1 -0.2": ["modernities"], "16.2 8.4 16.4": ["surfies"], "12.8 2.4 23.0": ["picklers"], "8.2 1.5 13.0": ["glassybaby"], "9.3 8.3 15.5": ["lawbook"], "-4.7 9.1 11.9": ["osteochondromas"], "20.3 8.0 5.3": ["froman"], "7.6 1.9 3.7": ["recharacterizing"], "8.3 4.2 -7.3": ["orporate"], "14.4 16.7 11.0": ["globa"], "-5.6 5.3 5.9": ["selectperson"], "11.5 12.7 27.1": ["yngling"], "9.1 4.2 -2.2": ["organistation"], "-1.2 4.1 3.9": ["firemaster"], "1.6 6.1 5.1": ["unformat"], "6.9 12.7 6.4": ["shanda"], "4.0 0.8 11.5": ["everett"], "4.5 9.7 -0.8": ["chargee"], "-4.3 9.9 9.5": ["arsenicosis"], "3.4 21.8 4.3": ["saffronites"], "1.1 8.8 3.5": ["hiscareer"], "11.9 1.9 6.5": ["quarterpanels"], "10.3 5.9 15.3": ["mierda"], "-5.3 2.0 4.3": ["drirelease"], "2.3 11.3 15.8": ["xanthophylls"], "3.6 15.4 12.4": ["bihari"], "11.7 2.0 4.2": ["nieuws"], "12.7 14.0 38.0": ["mudsnail"], "7.3 3.9 3.7": ["sheding"], "6.2 17.8 23.0": ["mautam"], "12.9 8.6 12.7": ["xylophonist"], "2.9 -3.1 9.7": ["hydroxybutyrate"], "-3.0 2.5 3.8": ["flowrates"], "-5.6 1.1 1.2": ["sood"], "7.7 10.3 -2.0": ["fraudlent"], "14.2 20.4 12.4": ["posion"], "11.1 2.4 1.9": ["linacs"], "2.8 12.7 -0.6": ["contect"], "16.7 14.9 13.7": ["awiggo"], "20.3 7.5 14.7": ["gyrocompass"], "12.0 7.2 3.7": ["wooers"], "7.6 10.6 26.2": ["chamise"], "11.9 10.5 10.6": ["foglight"], "-3.0 21.6 9.4": ["sipahi"], "5.7 3.2 8.3": ["reprt"], "-1.9 6.2 10.8": ["maayo"], "1.1 12.1 7.1": ["nominalism"], "5.5 3.3 5.0": ["choirmasters"], "7.2 9.3 13.5": ["junketeering"], "5.0 13.9 14.6": ["reissuances"], "12.6 2.2 12.3": ["lune"], "11.4 -0.3 -7.6": ["youchange"], "-3.7 -4.6 8.3": ["popula"], "14.9 15.0 26.6": ["bushbabies"], "3.3 8.3 6.2": ["untalked"], "4.0 6.0 0.2": ["appelation"], "5.2 15.4 13.8": ["oleuropein"], "13.8 3.5 16.8": ["backwall"], "-6.6 15.1 -2.4": ["allowe"], "12.7 15.2 20.9": ["euonymous"], "11.1 6.8 18.9": ["bluets"], "-9.3 8.0 10.7": ["interzone"], "9.9 7.0 13.5": ["fastbacks"], "1.9 6.2 12.1": ["jigi"], "9.0 -1.9 28.8": ["beargrass"], "3.9 5.1 10.2": ["daybooks"], "13.4 1.6 7.1": ["abbyy"], "2.3 8.7 18.0": ["termiticides"], "4.8 5.6 8.0": ["sploitation"], "9.5 10.2 19.4": ["weddin"], "3.3 9.5 11.6": ["teache"], "23.5 10.0 7.0": ["moonroofs"], "-0.6 6.2 2.4": ["rooke"], "9.0 14.6 9.2": ["abdominally"], "-1.6 3.4 6.5": ["opprtunities"], "0.7 -6.9 7.7": ["silverwares"], "-1.2 5.5 4.1": ["dislodgment"], "11.6 12.0 30.4": ["paku"], "-2.9 4.9 13.1": ["ryung"], "7.0 25.5 6.1": ["mainsprings"], "18.9 14.0 15.8": ["cuddlesome"], "9.8 21.8 10.3": ["mase"], "6.9 16.6 6.3": ["subsidences"], "5.5 -5.3 6.9": ["seasion"], "16.8 11.8 16.2": ["planetesimal"], "18.5 -7.6 11.6": ["ozonated"], "8.8 7.5 0.8": ["multicount"], "-1.3 13.9 13.2": ["automaticaly"], "8.5 -2.3 5.0": ["premios"], "12.1 16.0 15.7": ["foppery"], "5.0 14.2 15.6": ["recumbency"], "1.5 7.2 8.2": ["intergranular"], "4.2 4.6 7.7": ["wone"], "-13.8 8.3 -8.4": ["knwon"], "5.8 -1.4 7.3": ["cardmaking"], "5.1 13.3 33.7": ["specklebellies"], "4.9 12.2 -0.7": ["decibles"], "14.4 12.1 15.6": ["snotting"], "1.5 5.7 5.9": ["torahs"], "7.6 16.4 5.0": ["restrategise"], "2.4 20.1 10.9": ["heartrendingly"], "8.6 7.9 5.1": ["historicizing"], "25.3 16.7 28.0": ["glowworm"], "9.1 5.6 7.0": ["cloxacillin"], "19.3 12.5 13.4": ["manimal"], "12.1 -0.5 14.9": ["vinasse"], "11.8 4.4 13.1": ["postbubble"], "4.2 13.5 0.1": ["theincident"], "6.1 3.7 4.3": ["fier"], "5.7 -1.6 9.2": ["construc"], "10.0 9.8 5.3": ["exciteable"], "7.8 -2.4 11.4": ["safle"], "1.5 9.0 -1.8": ["overblocking"], "10.1 18.6 11.3": ["photochemically"], "9.5 9.4 42.3": ["zukes"], "10.1 18.8 30.0": ["woodwasp"], "11.0 22.7 4.5": ["nuclearism"], "1.7 5.8 10.9": ["longtimer"], "1.8 24.3 21.3": ["navigationally"], "10.7 4.4 10.3": ["ocks"], "4.9 0.3 1.6": ["mandation"], "7.0 27.7 15.8": ["serously"], "4.0 18.7 12.6": ["wuold"], "3.1 6.8 9.9": ["prague"], "8.3 6.3 2.2": ["transation"], "9.6 6.5 18.7": ["turnkeys"], "-8.7 11.6 -0.7": ["apprehendee"], "12.3 15.3 14.5": ["clappin"], "2.0 25.1 10.8": ["rationalities"], "15.0 26.0 12.2": ["kumbayah"], "-5.1 -1.5 -2.2": ["putforth"], "8.8 7.4 17.3": ["fortifier"], "20.2 34.3 12.3": ["fragfest"], "10.9 8.9 8.2": ["chipscale"], "3.9 23.2 7.8": ["terible"], "28.2 13.3 12.7": ["botherers"], "8.3 5.5 0.1": ["counterfiet"], "4.9 4.8 8.4": ["chaussures"], "23.8 15.0 28.5": ["kaiten"], "7.1 5.5 18.9": ["nondeposit"], "3.1 6.0 9.3": ["longtrack"], "6.4 12.4 0.5": ["constructionism"], "13.2 1.7 15.0": ["boris"], "17.1 11.0 8.4": ["emoji"], "6.6 6.0 6.6": ["managementsolutions"], "-5.2 -1.4 11.0": ["cuers"], "16.3 -0.0 13.2": ["bargainous"], "9.0 3.8 11.7": ["azadirachtin"], "9.0 27.2 7.7": ["manouevring"], "3.3 6.3 -4.6": ["dharamshalas"], "1.1 9.8 9.3": ["undef"], "11.9 3.1 4.4": ["awaydays"], "7.7 3.8 13.4": ["koch"], "7.6 12.7 10.5": ["gradeability"], "12.4 -3.9 10.1": ["siks"], "11.4 1.8 13.7": ["wrights"], "11.2 9.7 9.3": ["extrudate"], "-3.9 3.1 12.3": ["classi"], "5.0 11.9 21.0": ["osculation"], "30.3 5.5 1.9": ["multibilliondollar"], "6.3 13.8 32.2": ["hamon"], "-8.6 5.5 7.4": ["nonpecuniary"], "12.4 -0.9 6.5": ["ultracaps"], "4.9 -6.9 0.7": ["methocarbamol"], "4.5 1.6 11.0": ["percentand"], "2.9 20.7 13.8": ["headsy"], "1.3 10.1 13.1": ["housemistress"], "11.2 8.8 15.3": ["interneuron"], "0.5 3.3 10.7": ["sitosterol"], "15.8 9.5 5.6": ["spoonfeeding"], "8.2 6.4 8.6": ["nup"], "-1.5 3.9 -2.5": ["fosbretabulin"], "4.5 0.8 4.6": ["liaision"], "10.2 0.9 3.3": ["olympiads"], "-4.3 30.2 2.3": ["salafis"], "0.7 19.9 5.5": ["firend"], "-0.2 6.5 10.2": ["tsaya"], "6.9 8.6 11.0": ["slumdweller"], "4.4 0.7 8.2": ["insertional"], "1.6 5.7 10.9": ["boxcut"], "9.3 8.1 10.9": ["richen"], "7.5 12.0 6.4": ["lachrymal"], "10.8 18.4 -0.3": ["plasmatic"], "0.7 0.5 10.1": ["bobingle"], "4.6 10.9 7.8": ["permenent"], "6.5 20.6 12.9": ["grimoire"], "1.2 5.8 9.3": ["fibrogenesis"], "14.4 9.5 16.0": ["bashi"], "0.7 23.5 1.3": ["perosn"], "3.3 9.0 -0.8": ["clivatuzumab"], "8.4 21.4 11.3": ["mythologists"], "17.6 -3.0 -5.0": ["partnerhsip"], "4.7 12.1 12.0": ["sevengame"], "2.4 2.7 14.0": ["thiamethoxam"], "5.7 12.4 12.9": ["inute"], "13.1 9.1 14.9": ["dovecot"], "13.2 2.1 -2.9": ["finetunes"], "19.8 12.7 19.6": ["aitches"], "9.8 7.4 14.1": ["jetes"], "-2.7 -5.5 -1.8": ["mdec"], "-4.7 1.4 16.4": ["prasterone"], "-4.5 7.4 4.6": ["virologically"], "20.2 0.7 18.8": ["electra"], "8.9 1.7 -3.1": ["azimilide"], "11.3 0.0 10.5": ["forone"], "4.3 3.4 14.3": ["amet"], "3.9 2.4 10.6": ["tober"], "9.4 7.0 11.9": ["beguinage"], "10.8 13.2 18.1": ["embyros"], "6.2 13.9 22.6": ["starvin"], "16.3 17.8 18.0": ["torpidity"], "17.1 6.5 8.3": ["slatwall"], "6.2 12.9 8.8": ["heartsore"], "1.1 8.5 17.0": ["prepa"], "12.0 12.1 7.1": ["flywire"], "19.5 -0.1 1.2": ["bloodthinner"], "-1.4 -0.1 8.7": ["ureteric"], "15.7 9.9 11.0": ["aisleway"], "0.9 4.8 21.1": ["ferrate"], "5.8 11.8 9.2": ["dilational"], "6.0 13.5 15.5": ["longtree"], "-3.4 -2.2 3.2": ["zel"], "10.9 7.1 6.4": ["unprovens"], "9.4 11.5 13.1": ["erb"], "10.4 16.1 13.2": ["lawmkers"], "22.5 -7.4 6.6": ["gigabite"], "16.6 5.8 21.0": ["dormered"], "20.3 8.5 12.2": ["sellotaped"], "9.4 8.8 16.2": ["kuliglig"], "6.9 17.7 -3.0": ["reducting"], "6.1 7.8 8.8": ["defensa"], "15.7 9.0 12.7": ["beaty"], "15.9 6.4 10.8": ["poshly"], "23.2 2.1 18.8": ["gilted"], "11.6 2.8 30.4": ["marrons"], "10.2 10.3 12.9": ["unlubricated"], "25.8 13.1 26.1": ["slinkies"], "22.5 9.2 23.7": ["blankey"], "10.5 22.1 8.7": ["davevmax"], "7.6 14.2 16.1": ["sooking"], "8.5 2.9 -1.7": ["autho"], "9.7 -5.2 1.3": ["coiffeured"], "9.7 8.4 2.0": ["desing"], "9.4 2.5 3.6": ["gtnews"], "14.0 3.1 11.7": ["creditless"], "18.4 2.0 9.8": ["fremont"], "10.4 31.9 9.4": ["civilains"], "4.4 13.5 3.4": ["learnedly"], "17.7 5.9 10.5": ["theramin"], "7.1 9.3 10.8": ["amke"], "0.8 8.6 6.3": ["cusip"], "5.2 6.4 31.0": ["tribs"], "1.4 7.6 17.4": ["syempre"], "19.2 7.7 28.3": ["paska"], "9.3 6.0 28.1": ["kebap"], "7.2 15.3 12.7": ["dogies"], "6.0 22.4 7.2": ["elsewere"], "4.8 16.3 14.5": ["maculopathy"], "2.7 0.4 11.6": ["univer"], "11.3 9.5 35.2": ["spearer"], "0.3 38.5 7.1": ["amerikkkan"], "-3.1 -0.2 -1.8": ["lycees"], "5.0 2.9 15.1": ["telogen"], "-4.0 3.1 2.1": ["represenation"], "15.5 6.2 30.6": ["bavarois"], "11.9 5.7 14.0": ["tremblors"], "11.7 18.4 6.1": ["caracter"], "10.8 13.0 10.5": ["metamorphosized"], "-3.3 10.2 3.1": ["occation"], "13.9 -8.8 -2.9": ["adplex"], "6.3 -0.8 9.5": ["cais"], "12.7 4.9 3.2": ["covetted"], "11.1 14.8 7.5": ["powerdome"], "9.9 13.4 16.6": ["watcha"], "8.0 -1.3 9.1": ["handicraftsmen"], "15.8 41.9 8.2": ["wanzers"], "8.5 13.7 10.0": ["disppointment"], "-0.4 11.9 10.7": ["exhaustions"], "-4.1 10.4 9.2": ["manifester"], "-1.6 11.9 1.1": ["filmwork"], "-1.2 20.2 7.4": ["killedin"], "7.8 13.3 3.5": ["cordiale"], "0.2 19.5 8.0": ["pietist"], "17.4 8.0 11.9": ["nics"], "6.0 31.1 -5.2": ["manhunting"], "16.5 13.3 4.8": ["dysmorphia"], "8.6 13.2 20.8": ["mccarthy"], "-7.2 15.3 5.8": ["nonsuccess"], "8.4 11.9 5.5": ["rhapsodise"], "16.8 15.0 11.6": ["footedly"], "9.1 3.0 12.1": ["hydrogenating"], "-6.2 6.7 11.6": ["nandoon"], "13.8 22.3 18.5": ["georgie"], "18.0 1.8 40.7": ["hamour"], "11.6 9.8 8.2": ["bols"], "-7.2 3.7 2.6": ["etti"], "0.8 9.8 9.1": ["facemasking"], "-6.3 -4.3 10.4": ["compli"], "-3.3 -1.2 6.9": ["recoreded"], "4.4 16.1 8.6": ["nonevangelical"], "1.5 21.9 10.9": ["unmodern"], "14.5 2.0 10.2": ["loanbook"], "9.2 -3.9 7.9": ["becompleted"], "4.6 8.0 -3.9": ["multiposition"], "3.1 2.7 9.9": ["advair"], "6.4 -1.1 10.0": ["busline"], "1.5 6.4 18.7": ["eich"], "-0.2 20.3 4.9": ["witchhunting"], "-4.3 -4.8 -2.3": ["dorf"], "1.3 1.4 -1.3": ["markhoroszowski"], "6.3 8.4 10.2": ["pesambah"], "10.8 6.1 25.3": ["zonkey"], "14.7 6.3 8.4": ["urb"], "8.4 2.8 25.0": ["yerba"], "8.7 7.1 4.3": ["continuers"], "-2.0 3.3 4.3": ["isoproterenol"], "20.5 -1.4 16.7": ["midas"], "2.5 -3.7 12.1": ["semestre"], "15.5 14.3 10.3": ["nanopatterns"], "12.6 18.0 19.3": ["alerce", "galeforce"], "27.1 -3.3 4.8": ["lobbys"], "0.9 16.9 8.9": ["newsteam"], "12.3 14.1 26.5": ["aluminums"], "0.6 0.4 4.9": ["transesophageal"], "5.9 14.5 12.5": ["autotrophic"], "1.1 3.1 1.8": ["indemnitors"], "10.6 13.8 20.0": ["roughcast"], "15.4 10.5 38.1": ["razorbill"], "1.6 7.4 5.3": ["evra"], "-0.4 -4.2 -1.4": ["resultsof"], "4.3 17.1 16.9": ["shotters"], "25.0 7.1 13.7": ["foxtrotting"], "-5.3 1.4 2.2": ["asy"], "5.1 8.6 12.7": ["eharmony"], "11.2 12.1 13.5": ["robb"], "-9.4 2.3 -1.2": ["informativeness"], "13.9 8.3 18.2": ["tenons"], "2.3 6.7 12.7": ["dami"], "7.2 6.9 2.3": ["elgato"], "-3.2 -0.7 2.8": ["obert"], "-5.5 5.6 9.0": ["ild"], "16.9 14.6 22.9": ["kodo"], "-1.2 10.5 9.2": ["lazio"], "-4.7 14.3 6.0": ["zener"], "3.2 5.1 2.3": ["pense"], "-1.2 4.2 6.6": ["visilizumab"], "-4.1 14.7 9.4": ["suvivors"], "1.0 -0.9 5.6": ["decription"], "8.9 5.0 22.9": ["gamet"], "-3.3 17.9 1.2": ["ustadz"], "15.0 4.9 12.8": ["postdating"], "32.6 12.4 31.0": ["torosaurus"], "-0.6 4.5 -0.9": ["antihyperglycemic"], "-4.2 4.5 5.3": ["substitued"], "4.5 9.3 2.1": ["healh"], "8.0 10.7 13.1": ["kijiye"], "5.6 3.3 4.6": ["rolipram"], "10.8 14.5 2.3": ["undermedicated"], "5.8 1.4 3.4": ["growthand"], "-2.1 4.4 9.4": ["homozygote"], "13.4 35.1 1.7": ["infantries"], "3.1 15.7 13.0": ["antiregulation"], "1.2 12.7 10.5": ["iridotomy"], "10.7 15.3 24.8": ["baptisia"], "-9.1 -0.1 4.9": ["yed"], "13.3 7.0 14.8": ["udu"], "8.5 10.2 -5.2": ["supernational"], "-0.2 -2.2 18.8": ["sixtyblue"], "8.0 17.4 2.7": ["unstrategic"], "12.2 4.9 17.5": ["horno"], "6.4 15.5 14.6": ["microeconomy"], "-0.3 4.9 -0.9": ["ceived"], "5.9 5.5 18.4": ["farrowed"], "19.6 15.8 8.9": ["consipracy"], "2.9 18.1 14.7": ["passs"], "-2.7 4.5 6.7": ["underdeclared"], "9.7 19.2 4.7": ["policitians"], "7.9 4.5 29.4": ["lemoncello"], "2.2 -5.0 3.9": ["topbill"], "6.2 7.7 7.0": ["iyi"], "4.9 8.6 12.4": ["reem"], "-6.0 17.5 11.0": ["nohow"], "9.8 19.3 12.3": ["queasier"], "5.5 16.7 12.9": ["portugese"], "9.9 15.9 5.5": ["hutzpah"], "18.5 13.2 22.0": ["growable"], "-3.5 6.8 12.0": ["antimetabolites"], "3.1 17.3 3.1": ["paricularly"], "-8.2 -4.0 -19.1": ["explaind"], "21.3 8.9 12.2": ["metopes"], "8.5 1.5 3.4": ["winxp"], "16.9 21.2 15.6": ["hivemind"], "18.2 12.2 27.8": ["ringtails"], "5.9 6.5 9.9": ["fotonovela"], "-7.8 2.5 0.1": ["nominals"], "2.0 8.1 7.8": ["norwich"], "1.7 6.3 2.1": ["ingilizce"], "9.3 11.7 5.2": ["arival"], "3.7 -2.2 -0.3": ["cse"], "0.4 6.9 10.9": ["facialists"], "13.1 3.4 43.1": ["huss"], "2.7 11.1 14.7": ["mija"], "10.4 3.8 14.5": ["tigre"], "11.5 11.4 10.5": ["fleshpot"], "8.0 30.3 2.9": ["unpatriotism"], "-0.0 -4.2 8.9": ["pce"], "16.4 16.5 33.5": ["fishiest"], "-0.4 4.5 12.6": ["diaphysis"], "2.2 3.6 7.0": ["speedballing"], "-3.6 13.7 3.9": ["arrythmias"], "-2.5 2.3 -0.9": ["associateship"], "10.4 16.0 4.1": ["sprited"], "1.3 17.9 9.0": ["hlep"], "0.1 2.9 -0.2": ["regardingthe"], "13.6 15.1 24.4": ["unchilled"], "-4.3 -0.6 6.7": ["iew"], "18.0 4.1 12.7": ["analsyts"], "13.4 42.8 2.6": ["mujahedeens"], "1.7 4.9 9.8": ["eightth"], "7.7 -2.6 13.8": ["laundrywoman"], "8.9 0.3 5.2": ["swissnex"], "3.1 18.0 17.9": ["carlson"], "9.1 11.1 5.0": ["nullities"], "9.7 13.2 21.0": ["popcorning"], "9.7 13.3 10.0": ["supervirus"], "5.9 29.7 2.2": ["powerholders"], "-0.2 7.2 7.0": ["execise"], "11.6 9.2 10.7": ["hyrdo"], "-3.8 6.9 10.9": ["sassi"], "4.2 26.5 13.5": ["opions"], "14.2 2.7 12.3": ["electrofunk"], "4.4 4.8 6.4": ["photoprotective"], "1.3 2.5 7.1": ["especialmente"], "12.3 6.2 11.7": ["webbings"], "8.7 12.1 -1.3": ["telecollaboration"], "1.2 2.2 -0.3": ["asaid"], "-2.9 -8.1 -4.6": ["airchecks"], "7.8 12.6 -0.6": ["reult"], "6.2 -3.8 10.0": ["wasterwater"], "8.1 -1.3 12.0": ["boattail"], "6.2 15.0 1.2": ["leetspeak"], "25.0 1.2 8.1": ["moneyspinning"], "7.0 18.2 17.7": ["showshoes"], "9.4 28.7 3.6": ["manpads"], "-0.2 2.1 15.5": ["proseccos"], "0.0 2.1 8.8": ["piperazines"], "3.3 3.0 11.9": ["activesync"], "5.7 13.1 3.0": ["acussed"], "4.9 3.0 3.6": ["slapgate"], "-1.7 18.3 3.7": ["fianlly"], "0.8 8.0 15.2": ["sultrier"], "7.1 1.8 7.7": ["paypoint"], "6.4 7.1 13.0": ["turfers"], "7.1 16.8 8.9": ["unrepented"], "14.7 25.2 14.1": ["throe"], "2.3 11.8 13.6": ["slapjack"], "0.9 -4.7 -5.1": ["inbusiness"], "4.0 12.3 3.0": ["aeroacoustics"], "11.1 5.0 22.5": ["inliners"], "15.1 5.4 20.8": ["zink"], "10.2 14.9 17.7": ["hilltribes"], "8.2 11.5 5.3": ["ront"], "7.2 22.9 9.8": ["amasing"], "14.7 0.8 1.2": ["subsi"], "-3.6 19.6 13.5": ["ackward"], "20.1 19.6 15.9": ["sickled"], "11.2 7.8 26.6": ["stegosaur"], "-2.6 1.9 13.8": ["antral"], "6.1 9.1 10.3": ["baccha"], "14.5 3.5 13.8": ["mispackaged"], "10.4 23.4 5.1": ["deterant"], "3.2 8.1 6.8": ["protofeminist"], "9.6 16.5 14.1": ["adreneline"], "2.6 10.1 3.1": ["legalizations"], "9.9 12.4 13.4": ["subtended"], "12.9 6.6 24.3": ["ival"], "4.0 7.6 2.4": ["davon"], "2.3 16.7 5.6": ["reentries"], "19.0 16.3 11.1": ["reccession"], "34.0 7.5 14.6": ["techdom"], "1.6 21.7 7.1": ["ustads"], "-4.5 8.6 1.8": ["krishnan"], "7.3 11.4 12.6": ["millwall"], "-4.5 10.0 10.3": ["speedwatch"], "13.3 10.3 21.9": ["subseafloor"], "7.3 15.5 6.6": ["explitive"], "2.2 2.7 12.7": ["cuprite"], "2.3 -5.5 2.8": ["uly"], "1.8 0.1 13.0": ["cular"], "11.2 9.8 7.7": ["kindler"], "6.9 7.9 6.8": ["domal"], "6.9 14.0 19.1": ["incroyable"], "13.7 2.7 3.6": ["phonogram"], "10.0 14.5 11.8": ["subdial"], "16.5 8.2 16.6": ["spinneret"], "4.5 14.9 11.6": ["chikunguniya"], "1.6 -14.6 -2.0": ["bioresin"], "6.8 6.5 1.7": ["endorsable"], "-5.8 6.0 1.4": ["pse"], "10.3 15.1 18.2": ["accer"], "23.2 7.8 11.9": ["weeble"], "15.0 14.3 23.5": ["humpin"], "7.9 14.2 4.6": ["monoculars"], "10.0 10.5 15.9": ["tagalog"], "13.0 -3.2 8.4": ["gymslip"], "6.1 13.3 15.0": ["mackin"], "12.2 24.5 17.2": ["toerag"], "6.4 12.2 7.6": ["kifaya"], "-2.2 2.7 10.5": ["ause"], "-4.3 6.4 12.4": ["hyperstimulation"], "9.5 5.8 9.4": ["utilizar"], "7.4 6.0 10.0": ["sortir"], "8.2 16.3 12.7": ["fastnesses"], "-0.9 29.1 0.3": ["divisionary"], "6.6 8.1 12.8": ["dagen"], "13.7 6.3 18.4": ["oryxes"], "1.0 -4.9 5.7": ["prif"], "13.1 1.4 -0.4": ["remutualisation"], "-3.7 -5.1 -0.6": ["knet"], "4.9 7.4 11.5": ["helicity"], "15.1 18.3 21.5": ["dampish"], "1.8 -2.7 5.5": ["gug"], "15.7 11.7 27.1": ["bokashi"], "4.6 7.6 0.5": ["asthama"], "11.8 0.0 4.7": ["septugenarian"], "8.2 3.2 1.6": ["ecarlist"], "12.1 14.7 19.8": ["chitter"], "13.4 11.0 21.1": ["grandifloras"], "2.8 10.0 6.9": ["menon"], "8.4 4.0 23.2": ["chalkiness"], "0.2 2.3 13.7": ["jista"], "30.1 8.2 27.6": ["horsehead"], "17.1 16.2 16.7": ["playfight"], "13.6 14.8 3.3": ["deafer"], "-0.1 11.3 9.4": ["wickettaker"], "7.6 7.2 9.4": ["linears"], "13.7 13.1 7.8": ["stoppies"], "5.8 8.1 -2.6": ["pdb"], "-0.2 4.7 6.8": ["olb"], "7.5 4.2 30.4": ["lugaw"], "15.7 12.4 5.4": ["infalling"], "7.7 -3.8 12.7": ["methyltestosterone"], "10.3 2.8 -2.7": ["coresystems"], "7.3 11.5 12.9": ["suarez"], "-0.9 7.7 12.9": ["oportunidad"], "-2.4 12.2 12.4": ["picong"], "3.4 0.5 0.9": ["livein"], "16.9 14.3 12.2": ["snowthrower"], "12.8 26.9 13.1": ["uzis"], "-4.4 6.6 2.5": ["neoplasias"], "12.3 6.0 4.3": ["refixing"], "6.4 10.7 4.1": ["valeurs"], "0.0 7.7 11.9": ["pythagorean"], "-3.2 -1.2 10.3": ["kameezes"], "9.6 5.9 11.5": ["microgel"], "12.7 2.1 3.0": ["nment"], "6.2 20.0 -0.9": ["rapproachement"], "14.3 7.8 -0.6": ["polygraphic"], "15.8 11.1 16.8": ["pointin"], "3.3 0.8 10.8": ["riderships"], "24.9 15.5 23.3": ["mahoganies"], "3.7 3.9 11.9": ["fiirst"], "15.9 8.7 18.2": ["ungloved"], "8.2 10.8 10.2": ["tunning"], "1.1 -1.9 2.7": ["cardbus"], "0.1 3.3 17.0": ["butanes"], "9.6 28.8 3.9": ["oftimes"], "-2.9 14.8 2.3": ["mprodigy"], "22.1 12.3 13.4": ["blurp"], "6.4 -1.0 7.8": ["sodes"], "9.3 3.1 -0.8": ["investissement"], "7.9 16.4 12.9": ["pulpier"], "4.1 13.0 15.9": ["wjksea"], "14.0 2.8 11.3": ["thestock"], "13.0 3.2 6.2": ["mmu"], "13.5 4.9 17.9": ["jootis"], "-4.8 14.8 3.1": ["anaphora"], "18.7 2.9 11.3": ["pocketless"], "15.0 13.0 36.0": ["canoli"], "1.4 10.8 0.7": ["reshelve"], "3.8 7.7 6.4": ["villag"], "9.4 10.2 11.2": ["pyrrolysine"], "15.1 4.0 10.1": ["refridgerators"], "18.5 7.2 25.9": ["shama"], "-5.4 10.7 5.3": ["testatrix"], "5.6 10.3 2.2": ["guitly"], "4.4 11.5 -1.2": ["scintillators"], "20.1 8.4 13.0": ["funtastic"], "18.0 11.6 14.4": ["esophaguses"], "4.0 -3.8 7.2": ["inluded"], "-1.8 7.1 -4.2": ["accompanier"], "8.8 8.5 30.0": ["bharta"], "6.9 12.3 4.1": ["prerecording"], "-2.3 -1.4 9.5": ["recpath"], "6.7 1.9 3.5": ["pelletize"], "-2.2 -1.1 8.3": ["cmc"], "10.1 5.2 6.3": ["processive"], "8.9 8.8 17.6": ["tarsus"], "3.5 9.4 9.0": ["electrophilic"], "6.4 4.0 19.6": ["khaana"], "13.5 11.4 8.4": ["chanukiah"], "16.9 23.7 7.3": ["airbursts"], "7.8 1.1 14.3": ["fizzier"], "4.0 -5.0 0.0": ["designe"], "6.0 4.6 1.2": ["ifor"], "-0.4 1.4 1.2": ["amisulpride"], "7.4 -1.1 13.3": ["atmo"], "12.3 8.3 14.7": ["imaginitive"], "20.3 21.3 7.1": ["nowhereland"], "17.9 9.2 6.4": ["chunnel"], "3.6 0.1 9.2": ["cky"], "12.9 6.3 4.5": ["stairclimber"], "12.7 22.0 21.1": ["bodysnatchers"], "22.4 14.7 30.7": ["gluggy"], "17.3 7.3 2.2": ["hapten"], "1.6 1.4 18.5": ["seedsman"], "-0.9 6.2 0.6": ["baek"], "31.6 10.7 17.6": ["supertall"], "9.3 11.6 6.1": ["wwf"], "7.4 7.3 25.9": ["cumber"], "3.0 4.2 1.4": ["collegiums"], "16.4 5.1 44.2": ["cavatappi"], "14.9 9.3 10.4": ["exorbitance"], "11.3 11.0 7.2": ["faxers"], "4.0 2.6 10.8": ["expectaions"], "17.2 8.4 27.8": ["marginata"], "2.4 5.9 11.3": ["mantap"], "2.5 8.9 4.2": ["bce"], "7.8 5.7 25.8": ["logwood"], "6.7 1.9 8.2": ["neobladder"], "-0.8 -0.1 3.0": ["jayanti"], "5.0 9.0 -0.8": ["serializations"], "23.8 -4.0 11.6": ["fintech"], "4.2 10.4 9.6": ["inmany"], "-1.0 -1.8 2.7": ["parasitemia"], "8.1 5.4 5.7": ["orking"], "9.2 15.3 8.9": ["deadweights"], "-0.2 6.2 29.7": ["khichri"], "15.0 -2.9 12.2": ["quins"], "22.8 11.1 15.6": ["tonka"], "3.7 8.0 8.2": ["respuesta"], "4.1 4.3 5.5": ["bioscavenger"], "-1.6 5.2 2.1": ["pensionary"], "12.6 7.0 10.5": ["overthrust"], "0.6 10.0 16.7": ["reine"], "0.1 -8.3 -4.3": ["nial"], "5.4 4.2 11.9": ["tiple"], "-2.2 1.3 -0.9": ["sented"], "17.7 3.9 17.8": ["gourde"], "3.4 9.4 25.2": ["lakatan"], "17.4 4.4 2.5": ["magzines"], "17.1 -5.7 26.4": ["talong"], "9.9 13.8 6.3": ["tachymeter"], "4.1 3.7 12.2": ["aeroallergens"], "7.4 7.6 13.1": ["jamal"], "2.2 9.3 8.1": ["verschiedene"], "14.3 15.0 11.6": ["liquifaction"], "16.3 4.2 20.5": ["bandhani"], "12.7 7.3 16.1": ["resomation"], "-5.2 13.9 8.0": ["rangemaster"], "11.6 4.4 4.5": ["reproducer"], "11.4 31.9 20.5": ["multiplayers"], "4.5 8.9 16.0": ["magtrabaho"], "14.6 -0.1 -12.8": ["lanched"], "12.0 19.7 24.5": ["rhodos"], "8.7 7.3 30.9": ["farfel"], "-14.0 2.8 7.6": ["psychometrician"], "1.7 13.6 14.1": ["propria"], "5.6 9.5 12.0": ["malpositioned"], "-6.5 2.5 1.6": ["adrenomedullin"], "11.5 18.1 14.5": ["scambled"], "6.9 10.3 19.8": ["gaun"], "5.8 7.9 25.3": ["vitis"], "0.3 -3.5 9.5": ["teensploitation"], "4.0 -1.2 6.6": ["federa"], "-0.0 8.1 1.6": ["congnisance"], "6.3 8.8 22.4": ["fruitlets"], "-3.1 15.8 12.6": ["brownnosing"], "8.5 9.9 14.8": ["contaminents"], "4.5 11.6 -0.1": ["privative"], "2.8 -1.0 10.6": ["macdonald"], "-2.2 -2.2 9.6": ["ddwy"], "16.8 23.6 12.3": ["rudimentarily"], "-0.5 17.7 6.4": ["dissagree"], "-0.2 4.8 10.5": ["picornavirus"], "7.4 13.4 12.5": ["monoterpenes"], "8.9 8.1 13.4": ["nonhealing"], "-2.8 8.0 2.7": ["kwara"], "24.6 12.9 14.3": ["gormlessly"], "8.7 2.7 11.0": ["affiche"], "17.9 8.6 24.0": ["permitorium"], "7.2 1.0 14.3": ["citrix"], "9.5 33.5 7.7": ["ambusher"], "2.2 -6.2 12.6": ["lsland"], "-6.1 -0.8 7.3": ["harmonicist"], "-6.2 -3.8 6.4": ["pld"], "12.7 17.5 5.9": ["jambanja"], "14.4 -1.0 1.3": ["prnewswire"], "11.0 11.3 24.8": ["internodes"], "22.3 8.7 11.5": ["phoneboxes"], "0.4 6.7 7.5": ["bolte"], "8.5 -4.8 14.2": ["festi"], "3.3 11.6 7.3": ["competance"], "5.2 16.2 8.4": ["euthenasia"], "9.3 12.0 4.7": ["attmept"], "11.1 -0.0 13.2": ["reebok"], "2.7 14.6 9.4": ["usufructuary"], "10.6 10.1 11.9": ["fairwell"], "2.7 16.5 10.8": ["imaginal"], "9.6 8.4 2.2": ["monopods"], "4.2 11.5 19.1": ["masarap"], "-2.3 7.8 10.5": ["thrashier"], "-10.3 -1.2 8.3": ["licens"], "12.1 12.5 2.5": ["jocky"], "9.9 -0.2 9.0": ["bottlestore"], "10.0 5.5 -2.5": ["direclty"], "-2.6 0.1 8.3": ["pariatur"], "4.7 36.6 9.9": ["stealths"], "14.1 5.1 7.9": ["lowes"], "10.9 15.3 2.5": ["glorifications"], "12.1 3.2 20.6": ["shellmound"], "-5.2 9.5 1.6": ["adaquate"], "5.8 -0.4 -1.3": ["lant"], "16.7 2.7 18.8": ["cale"], "2.9 17.5 -2.6": ["triparty"], "7.2 15.5 2.4": ["soldat"], "-4.6 4.6 0.5": ["releasees"], "12.8 12.4 7.3": ["linespersons"], "-7.1 5.4 5.5": ["epileptologist"], "-0.6 -0.3 20.5": ["halaga"], "4.3 19.9 12.0": ["syllogistic"], "13.3 4.3 12.9": ["veline"], "17.9 11.3 3.9": ["technosphere"], "-9.5 12.1 14.9": ["continuer"], "9.2 12.6 17.7": ["varicosities"], "6.9 -5.7 2.0": ["vende"], "11.6 19.8 21.5": ["enviromentalist"], "-4.8 12.8 12.0": ["thave"], "2.0 9.4 7.5": ["extravagancies"], "9.2 1.6 12.0": ["oilcake"], "11.5 -1.9 7.8": ["barrelage"], "13.5 14.0 15.2": ["florigen"], "5.8 7.8 25.3": ["sonal"], "13.5 15.4 9.3": ["boobquake"], "-6.5 16.8 0.1": ["karyakartas"], "0.8 15.4 8.5": ["pentecostals"], "1.1 26.1 6.4": ["endureth"], "5.6 2.6 3.8": ["metallo"], "13.1 6.9 9.4": ["kludgey"], "5.6 13.0 3.7": ["carborane"], "15.6 -5.9 -3.9": ["aventis"], "2.9 8.9 0.1": ["htdocs"], "7.1 8.8 30.6": ["dauphinoise"], "-5.0 7.6 1.4": ["remised"], "-2.9 -5.5 3.6": ["nss"], "24.5 5.1 23.8": ["pogos"], "5.0 9.6 16.9": ["neurona"], "14.7 2.2 9.9": ["treadmilling"], "16.1 9.9 14.3": ["honeycombing"], "3.3 6.2 8.7": ["abar"], "12.1 13.0 19.0": ["sealevel"], "4.6 22.5 15.0": ["geezerhood"], "9.6 13.8 24.6": ["tuberosa"], "6.7 14.2 16.4": ["moonfaced"], "4.6 12.3 27.1": ["kishke"], "14.8 16.2 35.0": ["jawless"], "9.6 18.7 19.2": ["rockhead"], "21.4 8.3 32.0": ["chedi"], "7.3 7.5 4.2": ["nanostorage"], "0.9 -1.8 0.2": ["daughterboards"], "11.0 7.2 9.1": ["efectos"], "12.0 0.0 22.6": ["margs"], "20.0 7.3 1.6": ["fflick"], "6.6 -0.6 21.4": ["dhansak"], "-2.1 -4.6 11.6": ["streetstock"], "7.8 20.2 14.0": ["kishkes"], "4.3 3.2 6.3": ["usuarios"], "8.9 10.4 21.9": ["davidii"], "21.8 6.3 15.3": ["tinging"], "5.3 18.8 6.0": ["walle"], "7.9 -8.2 3.7": ["commerciaux"], "5.6 17.8 8.3": ["poeople"], "21.8 27.1 15.1": ["splosions"], "-6.9 0.8 2.3": ["schoools"], "24.3 10.5 25.7": ["leaflike"], "-0.9 1.7 5.9": ["miniumum"], "4.7 4.7 9.0": ["sterlisation"], "8.5 10.6 6.8": ["meaure"], "13.9 4.8 4.8": ["ericsson"], "8.3 3.0 9.8": ["douze"], "9.8 25.8 13.8": ["repetetive"], "15.3 10.0 17.5": ["globulars"], "0.9 28.4 5.4": ["bounderies"], "13.2 21.7 27.0": ["kinglet"], "6.1 20.0 27.3": ["seedtime"], "-1.3 4.8 -3.6": ["volvement", "administr"], "15.3 2.8 14.4": ["giftwrapping"], "10.0 -1.6 12.9": ["boxfuls"], "3.5 2.2 1.5": ["streetcare"], "1.5 -2.3 -10.7": ["gving"], "9.1 6.1 7.6": ["pihms"], "5.2 -0.1 17.0": ["brunched"], "9.0 -4.4 5.3": ["recente"], "7.6 4.7 3.9": ["touchmonitor"], "24.1 5.8 18.0": ["dolllar"], "11.0 6.2 1.8": ["goviral"], "25.2 11.4 20.3": ["squalled"], "-1.7 15.2 4.4": ["recordwise"], "-4.0 4.8 4.5": ["nondisruptively"], "16.4 19.6 -1.8": ["armtwisting"], "0.4 3.8 7.6": ["erent"], "2.9 2.7 2.1": ["monickered"], "9.9 3.4 23.1": ["trayed"], "-0.8 -4.1 2.6": ["habilitative"], "6.1 20.3 4.8": ["backwind"], "4.9 -0.7 5.9": ["cambelt"], "17.6 10.6 37.1": ["yabbie"], "5.6 8.4 16.3": ["chalcedonic"], "1.7 1.1 10.1": ["jungolf"], "6.2 18.8 -6.0": ["messege"], "26.0 7.0 9.5": ["moguldom"], "-8.4 -0.9 -0.3": ["nhf"], "7.2 0.7 13.6": ["explica"], "1.8 -2.0 -0.9": ["lected"], "-1.8 -0.6 10.5": ["dph"], "0.6 3.1 12.5": ["ople"], "4.1 14.4 13.5": ["astringently"], "18.7 16.2 31.1": ["buckbrush"], "16.3 20.0 1.9": ["heayweight"], "17.1 17.1 16.9": ["embanked"], "10.2 26.7 19.8": ["minehunting"], "-10.7 14.0 4.0": ["tefillos"], "3.8 23.4 8.2": ["soldados"], "-0.3 -4.3 5.7": ["lagta"], "3.0 -8.3 -6.9": ["relea"], "19.2 -3.3 5.3": ["onlne"], "9.1 21.4 15.2": ["noctural"], "6.5 3.1 5.3": ["volgens"], "14.0 1.8 10.1": ["vei"], "-10.7 0.8 7.0": ["interobserver"], "3.3 29.3 -8.6": ["coupist"], "8.2 8.2 11.9": ["flagmaker"], "9.9 6.9 -0.6": ["weiteren"], "15.2 10.1 19.1": ["dredlocks"], "7.1 8.6 24.1": ["spinosa"], "5.8 5.6 5.8": ["tinidazole"], "17.9 21.3 7.2": ["punchdrunk"], "4.6 8.2 7.7": ["sastra"], "2.5 -8.5 -7.4": ["ource"], "4.9 3.1 8.7": ["nuclide"], "5.3 10.8 9.9": ["flite"], "5.0 -0.4 13.0": ["flwyddyn"], "3.0 15.2 8.6": ["pansexuality"], "7.8 6.0 11.3": ["sexbomb"], "-0.8 2.5 22.3": ["soave"], "2.8 10.8 8.1": ["fleaflicker"], "5.1 4.3 11.6": ["nizatidine"], "7.2 9.2 22.3": ["essa"], "18.1 12.8 10.5": ["offshorers"], "18.3 16.1 12.6": ["clocklike"], "-2.0 19.8 11.4": ["immagine"], "3.6 7.2 11.5": ["heui"], "-0.5 5.8 8.8": ["ffitch"], "4.5 11.4 16.0": ["urbanities"], "6.7 5.2 15.5": ["wite"], "12.5 26.3 3.9": ["mii"], "-12.8 -3.7 13.0": ["cian"], "-2.6 5.4 4.5": ["sadhna"], "9.9 21.5 32.1": ["mezzes"], "12.0 15.9 2.5": ["chumped"], "9.0 11.3 10.1": ["afterburning"], "4.2 4.8 14.5": ["rockash"], "-1.7 4.5 7.9": ["tsaid"], "-9.6 5.4 2.6": ["asn"], "-2.9 15.2 15.9": ["photorespiration"], "3.8 3.8 32.0": ["bluecat"], "7.8 -1.0 7.8": ["microfilters"], "13.7 6.7 24.2": ["goldtone"], "2.2 1.3 2.6": ["guanidine"], "2.4 4.5 2.3": ["unescalated"], "6.1 -0.4 2.7": ["semaines"], "18.7 16.9 7.0": ["talkbackers"], "2.4 11.5 7.5": ["gaali"], "6.0 4.0 13.6": ["barco"], "19.5 5.3 37.2": ["saveloy"], "14.1 21.5 9.3": ["automobility"], "-0.6 22.9 -7.6": ["comander"], "0.6 0.3 2.4": ["conseils"], "13.5 -2.3 17.2": ["reclogged"], "8.5 7.6 3.7": ["saythe"], "3.7 3.8 11.5": ["nonskilled"], "12.7 2.2 4.7": ["shiteous"], "-6.9 16.7 6.6": ["overserve"], "18.3 7.9 25.8": ["kalamansi"], "8.6 3.9 19.7": ["fatima"], "2.2 13.9 6.2": ["gettig"], "16.8 20.8 24.4": ["spatchcocked"], "0.4 11.1 5.9": ["flipflopped"], "13.2 4.8 14.1": ["vibra"], "-3.8 10.2 10.6": ["ketua"], "9.6 24.2 19.9": ["seabasing"], "18.0 10.5 18.7": ["getty"], "1.7 5.5 -5.7": ["gangraping"], "-1.1 14.3 12.1": ["wellmeaning"], "7.1 9.5 24.7": ["culver"], "12.9 5.0 15.7": ["razy"], "18.4 2.4 8.6": ["bearproof"], "8.1 5.4 -2.0": ["supportthe"], "3.3 3.3 10.2": ["dav"], "9.5 7.2 22.7": ["agist"], "-6.4 -3.3 2.9": ["abstr"], "-1.8 7.2 2.0": ["sexters"], "9.5 7.6 14.1": ["drapings"], "16.5 14.2 18.2": ["townswomen"], "1.4 4.4 4.8": ["fansidar"], "8.4 21.3 1.8": ["alphanumerical"], "7.9 -2.1 17.8": ["vely"], "7.4 6.0 12.7": ["dihydrocapsiate"], "9.0 4.6 11.3": ["xeroxing"], "6.1 14.2 12.1": ["departements"], "-6.5 3.1 10.9": ["cumec"], "7.2 8.3 12.1": ["donnie"], "13.4 13.5 40.4": ["echinoderm"], "12.7 2.1 7.5": ["weepily"], "14.1 5.0 23.9": ["flav"], "6.7 -10.3 6.8": ["stoll"], "1.3 20.5 12.6": ["everyhting"], "10.8 -7.4 9.5": ["varie"], "19.2 -2.9 27.2": ["sicles"], "-3.7 21.8 1.5": ["arbakai"], "3.1 -2.6 10.1": ["monotechnics"], "0.1 -0.1 6.3": ["grantseekers"], "17.4 0.9 12.8": ["vegoils"], "7.4 -0.5 17.9": ["pomology"], "8.4 1.9 12.7": ["beatz"], "3.6 -3.4 -3.3": ["vjoon"], "0.1 13.4 9.9": ["katchi"], "8.1 -4.6 6.4": ["telenova"], "2.5 3.3 3.7": ["libera"], "4.5 -0.1 3.9": ["fixators"], "-1.0 5.3 4.2": ["anek"], "19.9 5.7 5.8": ["dermaceuticals"], "4.5 3.5 5.3": ["komplett"], "-0.7 -1.9 8.0": ["figo"], "9.3 16.8 18.7": ["mymalaysia"], "2.4 6.9 7.3": ["oxyhemoglobin"], "0.2 8.6 4.0": ["khul"], "5.6 21.2 3.1": ["unpursued"], "13.0 6.1 25.5": ["limeades"], "11.2 9.0 14.7": ["flutelike"], "6.3 21.8 21.6": ["calamaties"], "11.7 1.6 3.9": ["metalizing"], "6.8 12.8 5.7": ["calorimetric"], "10.0 0.3 10.2": ["radiactivity"], "-5.6 3.3 3.9": ["preintervention"], "1.7 3.0 6.2": ["etalon"], "11.7 14.6 13.5": ["swingingest"], "11.9 11.8 25.3": ["balsamroot"], "10.0 6.7 7.0": ["ratna"], "5.1 4.3 10.7": ["methylparaben"], "7.5 4.7 4.1": ["controversary"], "12.5 5.3 13.3": ["pokier"], "5.7 13.8 5.3": ["bonna"], "2.0 0.5 0.0": ["asembly"], "5.3 26.1 -0.9": ["comunist"], "-0.1 3.3 14.5": ["overexpenditures"], "-10.4 15.1 5.4": ["depoliticizes"], "6.9 3.6 14.1": ["trabeculae"], "4.1 7.3 1.9": ["freebirth"], "5.8 -1.4 7.5": ["orden"], "17.2 2.3 -0.4": ["readerboards"], "-1.0 3.0 19.9": ["pects"], "4.6 11.5 11.1": ["saathi"], "8.9 -4.7 4.9": ["spokesguy"], "-8.6 16.0 -1.0": ["chizuk"], "15.2 12.7 15.2": ["quincunx"], "-3.5 0.3 9.8": ["ncreased"], "3.3 17.6 0.1": ["soulsearching"], "8.6 6.4 12.1": ["multiterabyte"], "10.4 14.1 16.3": ["xeriscapes"], "-2.0 1.3 4.6": ["excitied"], "-3.2 0.0 4.7": ["vanpoolers"], "6.6 14.9 10.3": ["ultrabasic"], "10.6 18.5 7.9": ["karsewaks"], "7.4 16.9 10.4": ["celebrification"], "3.4 3.0 7.1": ["objectif"], "-1.2 17.6 4.2": ["surviver"], "5.9 4.6 6.6": ["roentgen"], "6.6 15.2 12.3": ["manje"], "-7.1 8.4 4.1": ["deafblindness"], "12.6 0.1 10.9": ["fluor"], "3.0 15.9 13.5": ["understan"], "12.3 4.9 10.0": ["sedimentologist"], "4.3 17.8 14.4": ["triduum"], "14.4 4.9 -3.5": ["abouit"], "5.0 14.6 -0.0": ["globalises"], "-1.9 0.7 4.4": ["telecourse"], "8.5 13.0 3.5": ["thranked"], "7.4 7.1 14.5": ["tendresse"], "3.2 7.2 4.9": ["opencut"], "10.0 8.4 38.7": ["ikura"], "12.6 4.0 0.1": ["tripmeter"], "0.2 12.4 15.5": ["tashlich"], "6.0 17.1 5.2": ["mesodermal"], "-0.6 12.2 8.7": ["myofibroblast"], "8.7 -5.3 6.3": ["successo"], "6.0 1.2 11.7": ["butylene"], "4.6 24.0 1.6": ["insuch"], "-1.2 8.8 13.7": ["mishra"], "12.2 18.2 17.8": ["antbirds"], "2.5 9.0 15.4": ["gagamitin"], "14.3 10.3 7.3": ["dryable"], "3.0 12.0 3.1": ["thesecurity"], "15.4 3.5 14.9": ["antimacassars"], "-2.7 5.4 -0.8": ["financialstatements"], "2.2 3.5 12.2": ["rigodon"], "8.3 5.6 3.0": ["kerbed"], "-5.4 5.9 5.0": ["microtarget"], "-5.3 -3.3 -4.0": ["demitting"], "-0.9 27.9 3.4": ["pacificism"], "-2.1 7.7 5.6": ["tenuring"], "-1.4 -7.2 6.0": ["rateof"], "11.7 2.8 33.9": ["pizzaiola"], "6.4 -7.2 5.9": ["laks"], "7.2 10.9 2.1": ["rigths"], "-3.1 5.8 6.6": ["jkun"], "11.4 12.3 19.9": ["shep"], "10.0 18.2 17.1": ["resillient"], "12.6 14.6 14.9": ["downt"], "17.4 8.4 10.4": ["bizmen"], "1.3 6.0 4.4": ["trimmable"], "3.9 9.6 24.2": ["xue"], "7.5 6.4 12.2": ["uuu"], "1.0 12.0 8.3": ["unchastity"], "6.6 5.7 40.0": ["culatello"], "9.9 2.4 17.6": ["iolite"], "9.8 -5.7 8.6": ["multiwell"], "6.9 3.8 4.3": ["alkylated"], "9.3 10.4 6.8": ["coure"], "2.2 1.6 -2.0": ["helsinki"], "-1.6 -4.4 3.5": ["prescott"], "8.0 7.3 31.5": ["myco"], "11.8 14.2 31.6": ["tofurky"], "13.3 12.8 8.3": ["redividing"], "17.4 4.6 17.6": ["skyride"], "7.0 -5.8 15.9": ["mesi"], "6.4 9.8 18.6": ["forkballs"], "17.2 6.2 17.6": ["verre"], "-6.8 11.3 3.2": ["adherences"], "3.7 15.3 0.4": ["takethe"], "5.1 20.5 8.3": ["accustoms"], "4.8 16.2 14.7": ["groundling"], "7.4 28.6 3.1": ["rightous"], "10.6 3.2 14.3": ["servir"], "4.1 8.8 8.7": ["bax"], "1.0 4.6 10.3": ["metasomatic"], "8.5 2.8 11.6": ["carbinoxamine"], "12.7 13.0 11.5": ["ultrarealistic"], "14.1 7.8 31.2": ["overfarming"], "-4.5 11.7 -1.3": ["thedistrict"], "21.8 5.7 35.8": ["arugala"], "5.7 0.7 10.7": ["siena"], "0.6 8.1 2.5": ["wasan"], "-2.0 18.0 6.3": ["ideality"], "9.2 -0.8 3.3": ["entrepreneuring"], "4.9 5.6 28.6": ["omlettes"], "-0.5 12.8 7.9": ["immunodominant"], "7.1 5.7 14.0": ["resevoirs"], "10.6 9.1 19.6": ["consession"], "8.9 9.8 14.9": ["rubbernecked"], "10.8 6.6 8.5": ["oxygens"], "11.5 8.7 16.9": ["pollera"], "-0.2 3.6 9.8": ["basel"], "-2.0 14.3 7.4": ["lood"], "18.1 10.2 19.0": ["scissorhands"], "5.3 14.5 10.7": ["ancelotti"], "5.1 13.0 24.6": ["okiya"], "8.8 18.6 16.0": ["jabailo"], "13.5 15.4 13.2": ["minidramas"], "6.1 1.6 16.3": ["ymlaen"], "17.3 9.1 9.1": ["sharklets"], "16.0 9.7 2.9": ["seismics"], "-0.2 4.7 0.7": ["humidicrib"], "13.9 1.7 9.8": ["winebar"], "18.7 1.5 12.4": ["scoopfuls"], "0.1 14.9 12.7": ["telangiectasias"], "8.6 -0.0 16.5": ["headstall"], "14.1 9.9 21.9": ["birling"], "10.6 7.7 11.6": ["pulloff"], "2.6 18.9 15.3": ["anya"], "1.4 2.4 2.0": ["hyperintensities"], "4.1 17.7 3.7": ["theose"], "1.2 2.3 6.3": ["cefdinir"], "4.3 -3.3 12.0": ["herey"], "13.9 16.6 18.1": ["rotovirus"], "4.1 24.2 14.1": ["wierdo"], "10.0 6.9 6.4": ["ancestoral"], "15.5 6.8 15.8": ["dholaks"], "18.6 3.0 18.4": ["trenta"], "0.3 2.2 12.6": ["pwesto"], "0.6 4.3 6.8": ["detrain"], "7.9 6.3 12.8": ["hyuck"], "2.7 15.0 22.3": ["gemma"], "-1.3 18.6 18.8": ["unsignaled"], "5.4 -0.8 10.3": ["sante"], "1.4 -5.8 -0.3": ["cessor"], "0.6 15.9 14.7": ["sks"], "19.6 14.8 22.6": ["rabbitbrush"], "0.9 -1.4 3.7": ["exellence"], "11.6 12.3 10.2": ["omdat"], "6.9 14.2 12.3": ["annularity"], "3.4 2.4 1.4": ["yeare"], "9.1 18.0 16.0": ["rodgers"], "-0.9 8.5 24.7": ["duckpins"], "5.7 2.6 -4.8": ["afirs"], "6.6 -1.9 8.1": ["eletricity"], "-1.3 3.0 22.4": ["tahi"], "16.2 4.3 6.1": ["gumstix"], "-2.6 4.2 0.0": ["ourse"], "1.7 3.9 11.3": ["neighborhing"], "5.8 10.0 9.2": ["repassing"], "7.2 21.6 6.9": ["unwon"], "15.9 0.2 12.6": ["museo"], "-3.5 2.9 1.8": ["rifamycin"], "2.5 11.2 4.5": ["weere"], "6.6 10.5 5.9": ["nof"], "10.5 3.6 8.1": ["sary"], "16.6 18.0 22.1": ["mouthes"], "9.1 4.0 9.0": ["integrale"], "-0.5 1.7 5.4": ["muxing"], "1.7 18.0 15.1": ["bromidic"], "-1.5 -1.4 2.7": ["essed"], "-3.9 12.4 6.4": ["bolometers"], "5.3 16.3 8.1": ["militares"], "7.4 7.0 23.7": ["lambi"], "0.6 16.4 20.2": ["botttom"], "11.7 4.9 18.1": ["buono"], "4.7 11.6 5.8": ["itinerancy"], "2.9 5.2 7.0": ["orthokeratology"], "19.0 9.8 21.7": ["lokum"], "1.4 6.3 26.1": ["spicily"], "11.1 3.9 7.3": ["celeron"], "12.3 24.7 12.7": ["misleadership"], "0.2 17.1 6.7": ["nonconfidence"], "-3.3 27.7 2.3": ["kunya"], "11.3 5.3 16.3": ["sideswept"], "11.9 12.9 9.4": ["muthaf"], "6.9 4.5 7.2": ["resticted"], "1.5 16.6 10.2": ["microphonic"], "9.2 22.8 14.5": ["pharisaical"], "7.2 8.3 6.8": ["sexualises"], "-2.1 14.2 5.3": ["premisses"], "2.7 3.0 2.3": ["solide"], "16.3 8.2 29.1": ["ideographs"], "9.4 8.5 12.8": ["butchy"], "-0.6 11.6 10.4": ["innigs"], "7.7 17.0 5.3": ["priding"], "18.6 16.5 26.7": ["ephemerals"], "8.4 10.0 2.3": ["verkaufen"], "13.8 1.0 19.2": ["pousse"], "6.6 -6.2 8.7": ["stry"], "15.2 19.1 3.5": ["lobotomizing"], "16.8 21.7 15.1": ["coralling"], "10.5 11.9 18.0": ["dishoarding"], "6.5 5.6 14.2": ["malic"], "-1.9 8.0 17.6": ["isipin"], "8.5 2.7 0.8": ["demonstartion"], "13.1 12.5 11.3": ["indistinctive"], "1.2 7.5 22.4": ["semidry"], "13.4 6.2 22.8": ["sempervivums"], "2.2 28.2 2.3": ["horsewhipping"], "16.7 10.8 26.1": ["chandleries"], "9.5 18.0 17.3": ["eart"], "4.3 7.1 1.9": ["perfluoroelastomer"], "3.5 3.1 7.2": ["phosphoinositide"], "8.6 20.3 10.8": ["willowers"], "10.3 3.0 4.7": ["ciclovia"], "-0.2 18.6 5.1": ["tooken"], "12.6 21.3 15.9": ["glissading"], "9.3 6.8 1.7": ["councill"], "2.4 29.0 10.0": ["misgovern"], "19.0 2.5 14.4": ["cigaret"], "17.8 11.9 6.9": ["handtop"], "18.0 -16.1 15.2": ["ofabout"], "3.6 18.9 0.6": ["questio"], "11.6 10.9 17.9": ["quella"], "14.4 2.5 18.3": ["kidskin"], "11.3 11.5 14.7": ["chilangos"], "5.9 3.9 2.7": ["techiques"], "0.7 14.5 19.8": ["meristems"], "1.4 6.7 13.1": ["favore"], "12.1 8.3 17.1": ["vajazzled"], "9.3 23.0 17.7": ["whitetop"], "14.2 12.5 24.4": ["felids"], "-2.1 19.7 3.1": ["fitrah"], "-12.2 2.8 13.3": ["remonumentation"], "11.4 13.1 13.4": ["bridget"], "4.2 10.4 2.9": ["hydrotreatment"], "13.4 3.3 12.9": ["micropipettes"], "17.1 12.3 28.5": ["noodley"], "16.6 -7.5 2.1": ["industrielle"], "2.0 9.5 6.5": ["chemoreceptors"], "17.1 14.0 23.1": ["gortex"], "9.8 9.1 20.1": ["fluey"], "6.7 16.1 11.7": ["mummery"], "14.0 8.8 17.0": ["alkies"], "5.1 0.5 13.1": ["craftmakers"], "15.9 10.2 10.0": ["commoditizes"], "12.7 4.2 9.7": ["marketperformer"], "0.3 -6.7 9.6": ["mscm"], "7.0 16.1 16.1": ["neatniks"], "20.2 11.1 18.7": ["marcel"], "17.2 11.1 19.4": ["antiquus"], "8.9 23.6 5.2": ["deepseated"], "6.8 19.4 16.6": ["weediness"], "9.6 6.8 17.1": ["caseinate"], "2.7 -2.5 11.1": ["voie"], "3.9 3.2 6.6": ["naprosyn"], "0.8 3.5 16.2": ["plowmen"], "-0.2 3.0 5.2": ["progestagen"], "3.9 11.0 -0.5": ["rogatory"], "19.6 13.0 10.4": ["watchcase"], "11.2 6.0 11.9": ["cartesian"], "4.2 5.7 4.6": ["downgradient"], "4.0 3.8 17.6": ["jadau"], "-5.8 13.6 13.5": ["interesante"], "8.7 22.8 11.0": ["midmatch"], "2.6 -3.7 -12.8": ["chiarman"], "13.4 7.0 14.8": ["muntins"], "-6.3 2.2 6.7": ["boscalid"], "7.1 6.6 8.3": ["toimplement"], "1.1 6.5 -0.7": ["reflectorless"], "14.6 6.5 3.4": ["irving"], "-11.8 8.5 0.7": ["reconized"], "13.0 21.7 9.6": ["brethen"], "13.6 -1.8 11.9": ["reaced"], "3.9 21.5 8.6": ["flatteries"], "11.0 8.8 10.6": ["prill"], "3.7 16.1 7.9": ["antishake"], "14.8 5.6 1.4": ["midomi"], "5.2 4.3 8.8": ["prebooking"], "10.7 5.2 14.2": ["makeunder"], "8.3 13.7 14.6": ["gans"], "8.9 3.4 32.1": ["cappelletti"], "2.1 1.6 5.0": ["coleaders"], "0.7 8.5 1.7": ["ellipsometry"], "19.9 1.1 10.6": ["enterpise"], "-0.6 14.5 -1.4": ["lavat"], "14.1 10.3 20.6": ["crinum"], "13.0 -2.3 -3.9": ["stie"], "14.3 5.3 12.0": ["bulle"], "8.9 4.3 1.0": ["kostenlos"], "7.6 28.1 5.0": ["unpredictables"], "20.1 5.5 -2.6": ["companythat"], "4.8 4.6 6.0": ["gamecard"], "5.1 8.1 24.9": ["furtakers"], "6.6 0.5 3.1": ["agred"], "12.0 14.4 20.9": ["plankhouse"], "6.7 -5.5 2.5": ["newscenter"], "3.9 11.4 8.6": ["bartonella"], "4.7 1.1 -2.1": ["tosedostat"], "0.7 1.1 0.7": ["faible"], "9.4 5.0 5.0": ["blackfriday"], "4.7 9.7 3.7": ["avaient"], "13.3 6.1 4.7": ["rollforming"], "4.6 6.3 8.6": ["myogenesis"], "13.9 22.8 28.0": ["landlubbing"], "4.4 6.3 13.1": ["schneller"], "6.8 11.6 0.9": ["contoversy"], "0.3 12.9 19.2": ["straplocks"], "4.1 5.7 7.8": ["blamable"], "8.2 15.6 17.5": ["counterpressure"], "1.6 11.0 12.8": ["seaason"], "13.7 19.3 17.1": ["gloms"], "10.8 13.8 0.1": ["abortuaries"], "9.4 -0.6 37.7": ["vitello"], "9.9 8.3 19.2": ["dentata"], "5.6 8.5 14.8": ["phlogopite"], "6.5 5.2 -5.2": ["publicities"], "4.1 3.7 9.0": ["lms"], "8.2 16.9 0.9": ["dsn"], "18.6 6.6 16.8": ["ionamin"], "0.0 6.2 5.9": ["underacheiving"], "13.0 18.1 25.0": ["rootbound"], "7.2 0.0 6.2": ["arcus"], "5.6 2.3 8.1": ["maltodextrins"], "2.3 11.0 -1.8": ["kindertransport"], "12.7 5.3 10.5": ["certa"], "4.9 5.5 9.6": ["retaping"], "-0.7 5.4 5.2": ["curriculm"], "5.9 15.8 15.0": ["waymarks"], "6.7 8.0 11.7": ["technolo"], "4.9 -1.9 16.2": ["tiveness"], "6.9 7.4 -5.9": ["wellpositioned"], "13.4 16.2 5.8": ["nauseam"], "-1.2 -8.0 0.0": ["roject"], "5.2 2.4 8.9": ["subvolcanic"], "4.8 8.8 23.5": ["roseus"], "3.3 12.0 9.2": ["desmosomes"], "-1.1 9.1 7.6": ["stretegy"], "12.5 13.9 6.5": ["mealymouthed"], "9.9 20.2 18.2": ["koscheck"], "10.4 9.0 -0.2": ["photoshoped"], "15.7 1.7 16.2": ["ultrasoft"], "4.9 8.0 2.4": ["quoters"], "1.1 11.1 10.1": ["socionomic"], "11.0 7.4 15.2": ["retrogene"], "-0.9 6.8 4.5": ["hosiptal"], "6.7 20.3 8.9": ["trival"], "6.0 0.8 9.4": ["multiphasic"], "7.0 13.2 6.1": ["pcworld"], "15.9 4.5 8.1": ["linescan"], "12.8 1.4 5.6": ["negocio"], "19.3 11.7 21.2": ["dripless"], "1.4 14.2 13.3": ["firmish"], "6.0 8.0 12.1": ["upton"], "5.5 7.4 6.6": ["inally"], "10.2 8.5 5.2": ["namelijk"], "18.7 -6.3 27.1": ["fritas"], "3.0 5.6 6.7": ["congrat"], "12.8 16.4 15.6": ["heaviosity"], "6.7 7.0 8.0": ["microfocus"], "13.1 10.4 17.1": ["sori"], "11.2 18.4 15.1": ["unmagical"], "-1.9 -1.6 -0.2": ["bothof"], "1.9 12.0 16.9": ["winespeak"], "17.2 20.0 3.7": ["maing"], "-3.1 0.8 13.5": ["publiko"], "6.6 8.8 9.2": ["partir"], "9.6 -3.0 23.9": ["romana"], "4.4 9.1 14.2": ["weighings"], "15.8 14.3 15.7": ["niblick"], "-2.2 -5.4 1.5": ["healthplan"], "-2.4 8.9 9.6": ["namak"], "10.7 -0.9 2.2": ["speculums"], "12.5 11.3 18.4": ["curtseys"], "7.7 -4.8 14.7": ["sbr"], "18.3 5.1 18.4": ["handleless"], "0.2 0.7 12.6": ["furth"], "15.1 -0.4 14.7": ["stilleto"], "13.9 17.0 11.8": ["crewe"], "4.6 10.0 12.4": ["reinterviews"], "19.0 5.1 10.8": ["villagey"], "4.8 -0.4 10.6": ["nonwriting"], "-2.4 29.8 2.9": ["atacking"], "26.5 16.1 21.1": ["viney"], "4.2 27.8 3.4": ["overawing"], "2.6 -1.8 3.6": ["scil"], "7.0 -0.6 13.7": ["bellevue"], "11.5 18.2 3.6": ["decolonising"], "7.2 7.2 23.4": ["wendell"], "4.5 9.9 7.7": ["merk"], "10.0 -7.8 11.6": ["tce"], "3.2 2.6 7.2": ["excitonic"], "12.5 6.3 17.2": ["actividad"], "7.4 14.9 11.9": ["basu"], "6.8 4.4 6.2": ["phpbb"], "4.7 11.0 0.2": ["voire"], "14.2 5.4 -0.7": ["megawat"], "5.7 6.1 9.5": ["nonproft"], "3.2 12.8 10.9": ["mycoses"], "13.3 18.2 15.0": ["burningly"], "2.5 -0.1 -6.2": ["mezuzas"], "7.0 13.9 3.8": ["dly"], "4.2 -3.4 6.0": ["jacques"], "13.7 25.7 25.5": ["pishing"], "19.6 8.4 21.8": ["ironsand"], "12.5 1.3 7.9": ["sectores"], "4.1 3.4 5.4": ["precycling"], "-10.9 2.0 2.8": ["intraobserver"], "-1.0 13.2 2.8": ["conneted"], "1.2 19.6 10.0": ["addeed"], "14.5 13.4 16.3": ["uncharming"], "24.2 15.9 18.7": ["dryads"], "-3.2 -4.0 3.4": ["lanreotide"], "12.5 32.4 22.7": ["magicks"], "7.5 6.2 24.2": ["goosefoot"], "21.4 7.2 9.0": ["casemod"], "-2.5 10.2 0.6": ["qari"], "3.6 5.8 14.2": ["sancharas"], "17.6 3.6 20.1": ["tuchis"], "7.1 8.6 10.9": ["fourpoint"], "1.4 7.5 8.8": ["caval"], "3.6 10.5 5.2": ["dhanda"], "8.9 3.8 6.8": ["divisionally"], "10.0 1.9 1.4": ["adserver"], "13.6 9.9 11.0": ["spiffily"], "10.0 8.3 24.9": ["grillmasters"], "-2.8 -6.7 3.0": ["educatio"], "5.8 9.4 10.8": ["reenforcing"], "4.7 4.3 -0.3": ["talksport"], "8.4 9.6 23.2": ["monkeyflower"], "17.7 10.5 10.5": ["macroscope"], "14.9 7.0 5.0": ["miniratna"], "0.0 0.6 1.6": ["tionally"], "13.2 -1.1 9.0": ["lucklustre"], "17.0 -0.8 15.7": ["wailin"], "16.7 -0.2 6.3": ["dispay"], "9.8 19.5 15.0": ["zud"], "22.0 4.0 22.5": ["dacron"], "5.5 16.0 14.2": ["troutfishyman"], "16.3 18.5 17.4": ["unsharpened"], "10.9 5.5 9.6": ["cricked"], "-2.8 9.3 6.2": ["saral"], "20.8 5.3 27.0": ["greaseproof"], "6.8 6.8 1.3": ["diisocyanate"], "9.0 17.6 17.1": ["moralised"], "21.0 5.5 19.1": ["moulin"], "9.4 -1.1 0.1": ["eurotuner"], "9.5 -5.3 16.0": ["grainfed"], "10.1 0.9 3.2": ["customed"], "7.5 7.0 7.6": ["jerrican"], "15.9 5.6 -3.8": ["iwork"], "2.0 -5.7 -2.2": ["stine"], "1.5 -4.8 6.6": ["meeet"], "16.1 8.7 3.7": ["bogger"], "13.1 5.9 4.2": ["workstyles"], "-0.1 -1.4 16.2": ["olo"], "5.5 4.9 10.1": ["diarra"], "3.0 10.0 12.6": ["yets"], "5.7 10.9 18.1": ["aly"], "4.4 11.4 0.0": ["grough"], "-3.8 3.8 1.4": ["tolerogenic"], "5.5 9.3 11.6": ["treking"], "-7.9 7.4 5.1": ["intradepartmental"], "7.5 7.9 3.9": ["ssue"], "7.8 8.0 13.9": ["matricidal"], "8.7 9.8 5.3": ["datamart"], "14.7 21.6 32.3": ["umbel"], "20.6 13.9 24.5": ["freekin"], "13.7 -1.6 -0.8": ["mgm"], "-6.6 5.8 2.0": ["donum"], "2.2 21.9 8.3": ["nonrational"], "9.5 8.3 10.1": ["langues"], "-4.5 1.5 7.6": ["thiopurine"], "3.2 19.2 7.4": ["partisanly"], "8.3 9.2 6.9": ["polycotton"], "18.2 17.8 15.9": ["bodhi"], "12.7 16.1 9.9": ["barganing"], "8.2 8.4 2.9": ["agnostically"], "5.5 12.7 15.2": ["decellularization"], "2.8 7.7 9.0": ["previo"], "3.5 10.3 2.0": ["emmigrated"], "16.5 4.7 10.6": ["shreddings"], "15.6 0.2 14.6": ["korner"], "0.2 12.4 9.6": ["miya"], "14.1 2.0 11.8": ["beerhouse"], "3.5 7.5 1.7": ["converstaion"], "2.3 8.5 -2.5": ["banega"], "11.2 2.9 13.4": ["consumo"], "27.6 19.9 10.3": ["gulpers"], "19.2 13.7 29.7": ["kuro"], "0.6 6.5 5.3": ["bibliometrics"], "12.9 10.1 28.9": ["piadina"], "-18.3 18.7 5.6": ["bereave"], "15.3 2.4 -1.7": ["videodiscs"], "6.6 10.3 1.4": ["ssues"], "5.8 9.9 13.7": ["sodales"], "13.2 10.4 29.3": ["froid"], "13.9 10.5 24.6": ["dinnae"], "2.4 7.8 15.6": ["assai"], "4.8 12.6 17.7": ["nanoglue"], "4.0 20.4 1.0": ["abinitio"], "3.1 12.2 2.8": ["glycophorin"], "10.9 0.7 11.4": ["alnico"], "6.9 8.9 1.7": ["armtwist"], "-7.3 -1.4 7.2": ["mell"], "0.2 8.0 0.8": ["poonch"], "20.0 5.1 24.4": ["pearlies"], "1.8 2.8 6.3": ["votable"], "7.5 10.4 20.1": ["newcasts"], "9.8 13.9 10.0": ["eurasian"], "6.1 -6.9 14.3": ["alameda"], "6.6 14.7 10.5": ["pyometra"], "7.6 13.7 10.6": ["whoot"], "14.0 4.4 24.0": ["fudgey", "morada"], "-11.0 -2.6 -10.5": ["rto"], "6.3 4.5 6.3": ["wanteds"], "12.2 17.3 6.5": ["infanticidal"], "0.0 6.3 3.4": ["infrasturcture"], "13.1 12.2 23.9": ["inkberry"], "8.6 12.0 4.9": ["heirachy"], "-2.6 2.3 1.3": ["unboosted"], "11.7 4.6 23.4": ["argali"], "14.8 32.1 9.0": ["superpatriots"], "10.1 17.1 24.2": ["acanthamoeba"], "-1.0 10.2 14.8": ["biaxin"], "11.3 -1.8 9.3": ["cartoners"], "15.8 13.9 18.8": ["vimana"], "9.7 0.9 3.1": ["radioligand"], "16.3 14.5 6.2": ["locha"], "18.9 2.3 9.1": ["sleeked"], "1.2 6.3 6.0": ["roval"], "3.4 16.3 6.3": ["transexuality"], "-5.9 0.2 4.2": ["kronnan"], "17.2 14.4 18.7": ["airgap"], "-1.0 15.7 5.7": ["downregulating"], "10.3 7.9 29.8": ["batchoy"], "11.7 10.2 6.6": ["hasalready"], "5.6 -2.4 11.0": ["cyhoeddus"], "20.9 5.9 19.9": ["demilune"], "9.9 22.7 7.6": ["regim"], "-5.1 3.4 8.6": ["chlortetracycline"], "22.5 22.9 14.1": ["arrrgh"], "-4.9 -0.8 5.5": ["mychoice"], "1.9 -1.5 13.1": ["ginagawang"], "10.7 8.9 14.0": ["chula"], "16.1 8.7 12.5": ["dustcover"], "15.6 10.1 18.5": ["lakesides"], "13.7 9.2 37.1": ["crookneck"], "-5.6 13.1 4.2": ["recompress"], "0.5 8.4 8.5": ["adsorber"], "8.3 -7.3 6.0": ["surg"], "10.3 -9.6 9.8": ["woodwaste"], "15.5 26.6 3.2": ["obsolescing"], "19.8 14.6 15.8": ["bumb"], "4.9 13.6 11.2": ["peroxidation"], "8.7 4.3 -3.2": ["counterclaiming"], "9.8 6.5 23.2": ["caracoles"], "7.4 -0.1 5.7": ["origianl"], "0.6 8.8 17.1": ["fumonisins"], "-2.2 -3.2 7.5": ["wph"], "9.4 12.6 3.1": ["opposit"], "10.3 0.7 15.2": ["nodders"], "4.6 1.7 0.7": ["origionally"], "5.6 4.4 0.7": ["amblyopic"], "-3.3 6.3 7.6": ["pyogenic"], "13.3 16.3 12.4": ["microresonator"], "14.9 13.4 19.3": ["ulcerating"], "-6.3 10.4 1.3": ["attorneygeneral"], "5.5 9.3 9.4": ["ordainments"], "9.3 9.8 14.5": ["kellythesier"], "10.3 22.5 3.8": ["infantilise"], "14.3 20.4 4.9": ["monoethnic"], "4.8 11.8 14.5": ["stochastically"], "5.5 4.3 14.1": ["tungstate"], "15.5 3.6 21.0": ["metho"], "12.2 28.4 11.8": ["hadji"], "-8.0 5.9 16.2": ["iyun"], "2.7 4.0 5.3": ["accumbens"], "12.5 12.4 11.8": ["swoonsome"], "5.5 15.8 13.3": ["brujo"], "-1.9 7.5 5.7": ["riting"], "7.2 -8.5 3.3": ["factboxes"], "0.2 3.7 4.3": ["minuites"], "7.8 20.1 12.9": ["ometimes"], "3.9 20.3 3.1": ["tandom"], "-0.1 1.2 5.2": ["siss"], "7.4 7.7 11.4": ["taxidriver"], "0.4 -10.8 -0.2": ["atmel"], "22.7 9.9 40.3": ["poboy"], "8.0 1.7 4.3": ["rallly"], "0.4 12.4 3.7": ["teling"], "6.8 12.9 7.9": ["politburos"], "7.1 22.8 8.7": ["cuntry"], "12.7 4.2 5.4": ["upby"], "2.7 10.1 9.5": ["dgmasker"], "3.8 -2.3 3.5": ["gymnatorium"], "13.5 -6.1 4.9": ["virtuosa"], "18.0 23.0 22.5": ["oiliest"], "2.3 21.4 18.1": ["wao"], "-1.1 9.8 0.5": ["femtozone"], "8.9 6.0 17.9": ["persica"], "-2.6 0.2 6.5": ["subchronic"], "16.5 15.3 26.5": ["jammie"], "4.3 11.6 16.9": ["dxy"], "16.3 6.5 5.9": ["fuelefficient"], "3.8 26.6 -3.4": ["unshakeably"], "1.4 7.8 16.4": ["bhee"], "24.2 25.2 15.2": ["quadrocopter"], "5.1 12.0 21.7": ["ashi"], "17.8 14.2 29.9": ["icescape"], "7.9 13.5 5.8": ["provocativeness"], "6.0 1.7 13.9": ["aumento"], "1.2 17.4 13.7": ["onsider"], "16.4 24.2 25.3": ["torii"], "18.9 0.5 10.4": ["diecasting"], "8.3 11.1 22.6": ["catting"], "8.7 13.3 16.2": ["jibbering"], "5.1 11.1 6.0": ["eurotopics"], "11.3 -6.5 27.6": ["grano"], "-8.2 -1.8 1.1": ["cta"], "7.5 5.9 17.1": ["churidaar"], "6.2 8.2 21.9": ["musterers"], "8.9 14.8 15.7": ["frontcountry"], "-0.4 3.9 22.1": ["packout"], "3.8 -2.4 7.2": ["excepto"], "10.4 2.0 15.6": ["jabot"], "-0.7 15.2 10.8": ["catechizing"], "6.0 8.7 4.4": ["metred"], "5.0 -3.4 14.4": ["cynnwys"], "14.5 5.1 11.5": ["pathy"], "6.1 23.6 6.2": ["irresponsibilities"], "-6.8 1.2 8.7": ["candidats"], "3.7 5.5 8.7": ["excessing"], "8.8 11.3 36.9": ["baigan"], "15.3 24.6 18.0": ["puker"], "16.6 10.1 1.9": ["negotating"], "3.8 6.4 10.7": ["gelo"], "-5.2 12.2 17.4": ["kasam"], "13.3 15.0 17.6": ["northwesternmost"], "1.9 18.6 18.0": ["yolas"], "3.6 21.9 8.2": ["megaman"], "0.7 3.5 3.6": ["ceux"], "0.9 1.1 10.0": ["writethru"], "-10.1 21.4 5.0": ["sitrep"], "14.1 24.3 7.3": ["posthumans"], "14.4 10.5 33.6": ["chilidogs"], "7.9 8.1 8.1": ["inquisitionnews"], "20.2 9.7 17.2": ["superballs"], "11.9 5.6 13.2": ["silagra"], "19.0 6.8 4.1": ["beavering"], "26.7 1.2 3.5": ["selldowns"], "18.3 4.3 20.8": ["onesy"], "14.2 13.8 7.1": ["infomania"], "7.9 6.1 -0.4": ["sportcaster"], "7.1 10.1 -1.9": ["thebenefits"], "1.4 8.7 16.6": ["laka"], "-1.0 6.8 10.7": ["dysmotility"], "4.4 8.1 17.9": ["deuterostomes"], "2.8 -2.1 2.5": ["quebecois"], "10.9 6.0 10.9": ["benchmarket"], "11.9 9.5 8.9": ["tracky"], "-0.9 9.3 15.0": ["whai"], "13.9 11.7 14.3": ["muchacha"], "6.1 14.5 20.0": ["shabka"], "-9.6 -5.4 8.1": ["teau"], "-2.2 8.6 9.7": ["eigenvalue"], "-3.2 5.6 13.3": ["journ"], "-11.3 -0.1 -4.7": ["ntly"], "-5.4 10.0 0.3": ["refamiliarize"], "1.2 7.5 12.6": ["testi"], "7.2 11.8 25.1": ["debeaking"], "10.4 6.2 6.3": ["przez"], "16.1 5.6 30.5": ["leatherleaf"], "4.9 3.4 11.4": ["draymen"], "5.9 28.1 10.1": ["anticommunists"], "11.5 -11.0 7.7": ["clai"], "9.6 -0.4 9.4": ["thermocycler"], "10.1 -10.4 15.2": ["jeen"], "3.8 7.3 9.9": ["juicio"], "24.1 8.1 11.7": ["miniture"], "7.6 16.6 -7.2": ["remanning"], "0.9 5.2 20.8": ["nangun"], "10.1 19.3 11.4": ["brokenly"], "-3.6 16.5 3.7": ["soteriology"], "14.8 16.6 19.9": ["goofus"], "20.3 6.1 28.0": ["jumbie"], "1.3 -0.5 6.4": ["includedin"], "9.7 1.3 15.0": ["thinpak"], "23.5 11.1 28.3": ["chunkin"], "6.0 8.6 11.9": ["params"], "5.7 0.7 9.4": ["jobhunters"], "4.9 14.6 8.9": ["withno"], "14.6 15.3 24.9": ["rattlin"], "0.1 4.7 0.8": ["commutated"], "11.6 14.6 8.3": ["jamahiriya"], "9.7 13.9 19.1": ["jonah"], "12.0 12.4 10.3": ["wilkinson"], "6.1 -2.0 5.8": ["rebill"], "8.3 18.7 4.5": ["firedamp"], "13.8 28.7 16.1": ["troopships"], "-5.4 17.3 5.4": ["situtaion"], "15.2 18.6 15.5": ["consuption"], "5.0 11.8 8.4": ["semifeature"], "4.1 20.2 13.7": ["bardo"], "7.4 3.9 18.0": ["shortboarding"], "18.1 15.1 13.9": ["californian"], "13.9 1.0 19.0": ["nanopatterned"], "-5.1 12.9 2.3": ["whensoever"], "11.2 23.9 18.1": ["incomprehensively"], "4.2 6.5 3.6": ["thedeath"], "2.4 15.2 10.9": ["actionpacked"], "4.7 8.2 23.6": ["brevirostris"], "13.1 13.8 11.9": ["nonsequitur"], "8.5 11.6 6.5": ["funtions"], "4.4 5.3 5.8": ["eins"], "-3.6 16.1 8.0": ["cytotoxins"], "-11.6 7.5 3.0": ["legue"], "10.8 10.8 13.8": ["umpty"], "6.7 11.1 3.8": ["misstepping"], "11.1 6.4 11.0": ["fatsuit"], "10.0 13.7 14.1": ["bzerull"], "11.8 26.7 9.2": ["exceptionalists"], "-2.1 2.4 13.6": ["mananalo"], "12.4 3.9 13.2": ["servingware"], "1.5 3.9 7.6": ["anolyte"], "10.4 2.6 4.4": ["propmaster"], "5.1 12.6 12.1": ["phuck"], "7.6 11.7 9.5": ["violencia"], "23.1 15.3 28.5": ["sangers"], "3.8 17.2 3.8": ["rojiblanco"], "5.2 -1.1 3.6": ["intraarticular"], "9.3 3.0 8.5": ["andproduction"], "8.5 12.3 6.9": ["obliterans"], "-7.8 5.4 0.4": ["siddurim"], "-0.1 22.5 11.9": ["binationalism"], "11.5 1.9 1.4": ["dualbook"], "15.1 5.4 39.9": ["chirashi"], "13.0 18.5 5.1": ["unlimbered"], "12.6 0.0 -6.4": ["onstruction"], "4.5 -1.1 7.3": ["prepolymers"], "15.9 14.0 20.3": ["bristlecone"], "2.4 -1.8 6.9": ["undenatured"], "5.7 18.3 -0.5": ["hadthe"], "16.0 24.0 1.3": ["metahuman"], "6.7 1.4 13.1": ["mwy"], "-1.5 -7.9 12.5": ["brownbag"], "1.7 -1.3 15.4": ["lumiere"], "9.2 8.5 19.3": ["tudo"], "1.1 9.8 5.7": ["privledged"], "4.3 1.7 5.4": ["recientemente"], "15.9 8.2 30.3": ["marinus"], "0.8 2.5 3.4": ["officiators"], "2.5 6.1 16.0": ["ischial"], "6.4 5.1 11.7": ["folker"], "13.9 10.3 17.9": ["pennywhistles"], "10.8 -5.1 4.3": ["rexine"], "10.8 21.4 14.8": ["unbelievingly"], "8.3 6.2 12.0": ["jedes"], "10.5 10.4 38.9": ["scaups"], "7.2 23.1 5.1": ["goatherder"], "8.3 7.2 9.6": ["bootspace"], "7.6 9.6 8.7": ["zeke"], "5.4 22.0 7.3": ["shewed"], "6.7 11.1 14.7": ["afi"], "4.9 23.2 6.7": ["partisian"], "7.8 22.8 10.5": ["mountaineous"], "8.5 15.2 11.8": ["frentic"], "1.3 11.0 9.8": ["concen"], "10.4 9.7 23.7": ["yarrows"], "-2.1 1.5 6.7": ["missense"], "1.5 15.4 16.2": ["hydrograph"], "-4.4 6.1 -5.0": ["investiation"], "7.7 12.1 11.9": ["commy"], "4.9 16.9 17.6": ["plantsmen"], "7.4 21.6 0.9": ["deranging"], "1.6 15.8 11.5": ["advertent"], "4.9 8.2 15.0": ["douchy"], "0.8 3.2 7.9": ["tiltmeters"], "3.6 6.0 8.9": ["schticky"], "3.1 -0.8 8.6": ["leadto"], "10.0 6.2 13.3": ["rockefeller"], "8.9 14.7 3.2": ["assange"], "11.7 16.9 6.5": ["fullhouse"], "15.6 4.5 3.1": ["mpx"], "6.2 4.2 14.9": ["tailshaft"], "4.9 12.3 14.3": ["naach"], "16.8 4.7 7.0": ["mogelijk"], "-0.0 -5.3 -1.6": ["dimesylate"], "7.8 -5.9 0.2": ["flurbiprofen"], "15.1 6.6 35.7": ["scuppernongs"], "-2.9 12.0 1.8": ["overdiagnose"], "5.3 11.4 8.9": ["wajib"], "9.5 1.5 19.6": ["arbi"], "2.5 5.2 16.2": ["resta"], "0.7 12.1 1.2": ["ofinterest"], "-1.8 -4.0 0.0": ["intercountry"], "5.2 11.7 8.2": ["braker"], "14.4 1.0 7.5": ["grandi"], "-3.1 2.6 12.1": ["mdwt"], "7.3 16.3 17.4": ["sachems"], "15.2 23.9 10.8": ["squirmish"], "10.4 6.2 20.7": ["curacao"], "5.5 -1.3 12.1": ["rispetto"], "8.5 2.7 10.5": ["semitractor"], "-0.6 2.1 5.9": ["eicosanoid"], "4.1 10.2 7.1": ["goernment"], "8.8 1.7 15.2": ["cubanos"], "10.7 18.4 8.7": ["chehra"], "-1.1 4.3 1.0": ["statementing"], "8.8 0.9 2.8": ["eaiser"], "-1.6 7.2 36.0": ["tyer"], "14.1 8.1 20.4": ["furls"], "1.6 -1.1 20.6": ["sorb"], "0.6 15.5 17.5": ["wlad"], "4.5 6.0 5.3": ["spotlessness"], "-2.7 11.8 -3.2": ["emphasied"], "7.1 11.3 10.9": ["nanobialys"], "14.9 12.8 19.3": ["brookeburke"], "7.5 19.8 10.2": ["superpest"], "13.6 13.0 18.6": ["arigato"], "7.4 0.4 9.8": ["micropatterned"], "12.5 5.9 16.6": ["totalisators"], "10.6 10.9 2.0": ["altenative"], "0.3 -1.9 24.4": ["graine"], "12.1 19.1 25.8": ["fuku"], "19.6 2.2 4.4": ["wipro"], "16.6 2.3 18.6": ["lacelike"], "3.5 24.4 13.8": ["pepperballs"], "6.1 10.6 10.8": ["capitis"], "-4.4 6.6 15.2": ["hypoglycin"], "13.2 6.2 31.2": ["suey"], "10.9 5.0 7.9": ["acceso"], "2.6 19.1 5.1": ["overstraining"], "5.8 5.5 12.6": ["alegria"], "6.6 5.5 4.0": ["inquorate"], "8.2 4.4 7.8": ["underbosses"], "6.9 5.0 10.2": ["volumed"], "0.6 -2.0 5.7": ["metallothionein"], "8.0 23.3 8.4": ["quailing"], "12.7 1.8 6.4": ["maxon"], "-4.0 -9.2 2.7": ["vement"], "9.5 13.5 2.5": ["critial"], "-1.5 -2.5 1.1": ["aker"], "4.6 21.6 22.2": ["anthropogenically"], "16.3 -1.3 2.5": ["classaction"], "12.8 14.1 9.4": ["fauxmance"], "10.2 -0.0 10.8": ["stylemakers"], "-3.2 6.0 7.7": ["leta"], "5.7 19.6 14.3": ["overprepare"], "2.9 9.4 23.5": ["muhammara"], "3.3 5.5 8.6": ["elminating"], "5.0 -5.0 -2.4": ["lafcpug"], "-1.1 22.4 12.6": ["spites"], "2.5 5.8 14.8": ["taghna"], "4.3 9.7 9.9": ["haftorah"], "10.0 4.8 17.7": ["slenderized"], "-0.1 7.1 2.9": ["itures"], "4.0 12.5 16.0": ["potiche"], "5.2 3.4 6.2": ["zippiness"], "9.8 0.9 13.4": ["colorblock"], "1.9 10.0 8.6": ["metaprogramming"], "10.6 10.5 49.8": ["drumfish"], "0.7 6.5 2.9": ["puskesmas"], "8.3 14.7 5.2": ["widefield"], "2.2 13.2 18.0": ["watu"], "-2.6 2.4 6.0": ["webstie"], "18.7 0.4 8.4": ["imprinters"], "9.1 3.2 37.6": ["pattypan"], "-9.5 18.6 -1.8": ["maqasid"], "6.1 16.3 16.9": ["evacs"], "1.4 0.5 3.8": ["avenir"], "-3.3 2.6 11.0": ["laborum"], "10.0 10.8 21.4": ["norris"], "9.3 -2.6 -2.3": ["commerces"], "16.5 9.0 17.1": ["famliar"], "16.1 7.7 6.8": ["adeal"], "4.8 22.8 12.8": ["localists"], "-0.5 22.2 10.1": ["thak"], "0.1 10.0 10.1": ["subsecond"], "10.7 7.9 4.5": ["majeur"], "14.5 17.7 21.8": ["northeasterlies"], "7.6 8.0 11.7": ["guapo"], "16.8 9.5 20.1": ["khus"], "1.3 7.7 3.0": ["compar"], "6.0 5.7 17.9": ["chokha"], "1.9 9.4 8.1": ["seien"], "-5.0 15.5 9.3": ["wehad"], "9.2 2.3 12.0": ["volleball"], "15.5 0.8 23.6": ["alkylphenols"], "4.8 3.0 6.5": ["chocri"], "-2.9 17.9 -4.9": ["instablity"], "9.4 8.9 6.3": ["carburizing"], "-0.8 13.8 6.5": ["ganj"], "8.4 13.6 18.1": ["entropion"], "7.1 1.7 3.6": ["chiffres"], "11.4 8.5 6.2": ["nehmen"], "10.1 5.0 9.7": ["nst"], "7.3 -2.5 11.5": ["cheeper"], "3.7 6.4 15.9": ["ramirez"], "12.9 15.8 10.8": ["manless"], "20.5 -2.5 17.3": ["paal"], "-1.8 24.9 2.8": ["terrorities"], "0.8 22.1 1.4": ["waterboardings"], "7.1 -7.0 0.2": ["superabsorbents"], "9.7 13.2 7.2": ["severals"], "14.0 9.0 7.1": ["magnetotelluric"], "17.0 13.7 8.2": ["despoils"], "6.7 18.2 11.1": ["tacke"], "-2.9 9.0 11.0": ["lastseason"], "6.9 -0.3 8.2": ["persone"], "8.5 18.9 19.4": ["closeline"], "8.7 9.7 24.9": ["pumpouts"], "-3.0 19.6 6.9": ["inconformity"], "-1.2 1.8 -2.9": ["theraphy"], "4.8 1.4 10.2": ["sano"], "29.2 16.4 17.9": ["spinney"], "7.6 1.8 14.1": ["darba"], "7.3 10.6 4.4": ["subnanometer"], "-1.8 2.7 8.6": ["hetastarch"], "17.6 17.3 30.9": ["andromeda"], "12.6 2.1 25.4": ["potjiekos"], "7.2 -2.0 -4.2": ["mutualization"], "19.1 12.9 11.3": ["lustworthy"], "7.4 6.1 20.3": ["sato"], "-1.3 4.8 5.8": ["explaned"], "-3.9 4.4 -2.2": ["bestpractices"], "-4.8 6.4 2.9": ["doublheader"], "9.2 -3.7 12.1": ["paleobotany"], "3.3 12.5 13.4": ["novak"], "-0.4 4.0 14.2": ["xanthone"], "3.6 12.2 0.5": ["aflotoxin"], "-2.3 16.6 6.8": ["contracept"], "1.6 8.1 3.9": ["keinen"], "10.9 11.7 9.8": ["doleiros"], "-7.3 5.0 -3.8": ["keyworker"], "4.8 9.9 1.3": ["sree"], "16.4 5.7 11.0": ["nonpilot"], "8.0 0.7 9.3": ["worksurfaces"], "-1.2 2.8 4.1": ["boni"], "6.9 10.1 -0.9": ["letzten"], "8.5 6.4 19.1": ["mccoy"], "-2.9 14.9 10.5": ["casus"], "7.2 0.7 25.0": ["tuak"], "16.0 0.9 9.7": ["agroindustry"], "16.5 17.1 20.7": ["biomineral"], "-3.7 1.9 9.6": ["venipunctures"], "-2.2 6.9 11.2": ["aab"], "6.4 3.5 14.7": ["durumagi"], "14.8 11.2 21.1": ["atlantis"], "-1.7 7.8 9.0": ["bilat"], "22.0 15.3 18.1": ["tricorn"], "-0.2 13.5 8.4": ["sattva"], "-4.6 2.9 7.3": ["technet"], "4.5 5.0 9.3": ["neurogenetic"], "6.8 10.3 20.8": ["praecox"], "-0.5 -0.1 12.3": ["peno"], "10.2 16.6 11.7": ["indelicacy"], "8.9 7.3 25.4": ["pirogies"], "5.5 6.2 5.3": ["shani"], "4.4 -3.4 -0.9": ["acesa"], "3.6 15.8 10.6": ["contrade"], "5.6 10.6 8.1": ["poltician"], "2.7 14.7 8.5": ["rowe"], "7.3 3.2 11.1": ["mujras"], "11.4 0.2 9.8": ["contiene"], "10.0 5.5 15.8": ["schatz"], "-9.7 5.6 4.5": ["panobinostat"], "17.3 7.4 17.0": ["hyraxes"], "12.9 9.2 7.2": ["resizeable"], "15.0 11.3 15.8": ["wowee"], "-0.1 18.9 4.1": ["frienemies"], "1.1 5.8 6.3": ["phansi"], "23.1 6.9 38.2": ["broasted"], "3.7 3.4 8.7": ["khayals"], "15.0 1.8 35.1": ["garganelli"], "13.0 10.2 -7.7": ["autoprint"], "13.1 9.0 30.2": ["poinciana"], "16.9 13.4 14.5": ["unpractised"], "1.7 1.2 6.5": ["preganancy"], "3.7 12.8 22.0": ["brassinosteroid"], "21.9 12.6 10.5": ["starscape"], "9.6 12.8 20.9": ["laila"], "13.0 12.8 30.0": ["morepork"], "10.2 22.9 8.6": ["negativists"], "9.4 8.2 18.0": ["loosey"], "13.8 1.9 5.3": ["begonnen"], "5.5 4.8 7.9": ["triplexers"], "9.2 12.5 15.0": ["manwhore"], "16.6 1.9 13.4": ["unstowing"], "6.7 15.3 13.6": ["edness"], "3.9 14.3 7.4": ["retcons"], "2.8 5.8 7.7": ["paradis"], "9.8 24.0 25.9": ["amphib"], "9.3 9.0 33.3": ["carolinensis"], "4.4 9.5 11.2": ["prophase"], "17.1 13.9 7.4": ["nonhistoric"], "7.9 -4.2 11.8": ["consum"], "12.1 19.6 -2.4": ["geolocating"], "8.9 7.4 26.5": ["foulies"], "-4.2 23.2 0.7": ["disparagements"], "2.9 5.5 5.0": ["cicerone"], "-0.5 20.6 19.8": ["woolgathering"], "5.9 -0.2 23.0": ["angpow"], "11.2 4.6 7.1": ["westend"], "26.0 11.7 25.7": ["mancave"], "-0.9 20.7 9.2": ["nonpenetrating"], "0.2 14.6 19.4": ["sericea"], "11.8 3.9 10.7": ["signmakers"], "-1.2 16.9 0.4": ["preoperational"], "-3.8 12.1 12.3": ["filmland"], "2.1 4.9 8.4": ["tarif"], "0.0 20.6 5.3": ["rami"], "10.9 13.2 9.4": ["ujamaa"], "1.6 2.3 7.2": ["ancienne"], "12.3 9.8 10.3": ["devore"], "-1.2 -2.0 -1.7": ["positi"], "14.9 17.5 22.8": ["tigger"], "-2.4 7.9 7.6": ["replicase"], "7.8 4.5 3.3": ["electromechanics"], "8.9 1.2 17.4": ["oki"], "7.3 14.7 9.2": ["stopp"], "12.4 5.9 33.7": ["rowi"], "20.3 11.0 35.5": ["scaleless"], "-0.5 14.3 6.4": ["inprisonment"], "0.5 16.4 12.9": ["scorewise"], "13.3 10.4 14.2": ["torianddean"], "0.6 6.8 1.9": ["anoymous"], "10.6 9.4 -0.7": ["kuduru"], "17.6 20.6 20.5": ["headscissor"], "5.9 12.3 7.3": ["uncustomarily"], "6.1 3.4 8.9": ["capitalizable"], "11.9 3.7 12.9": ["inutes"], "13.9 11.8 30.8": ["bigleaf"], "-1.4 11.8 1.4": ["aricle"], "7.9 14.3 15.8": ["roddick"], "9.0 14.2 26.7": ["wadeable"], "12.9 18.4 25.6": ["anting"], "-1.8 -3.2 0.7": ["erythropoetin"], "-2.3 3.0 1.2": ["haircolorxperts"], "-0.6 7.9 8.9": ["cyberbulling"], "14.4 4.3 19.1": ["palletisers"], "5.2 4.5 19.7": ["rollickingly"], "4.8 8.1 20.3": ["metsi"], "6.2 0.7 6.2": ["dbms"], "6.6 8.7 18.3": ["epigastric"], "-3.9 3.2 1.7": ["highbacks"], "20.6 5.8 38.9": ["frite"], "-0.1 11.8 8.2": ["trimeric"], "4.5 16.8 1.6": ["viv"], "0.4 8.8 18.1": ["asti"], "9.9 3.5 8.2": ["quadruplexes"], "-2.6 3.7 7.3": ["joinable"], "8.3 11.5 -2.0": ["tabloidisation"], "5.0 18.7 7.6": ["fonctionnaires"], "-11.4 15.0 3.9": ["rebbi"], "5.3 11.4 10.9": ["opentaps"], "15.2 19.4 6.1": ["immolates"], "9.0 -0.9 15.0": ["starchitecture"], "8.7 12.7 15.8": ["recaulking"], "6.4 -1.2 3.7": ["nanometals"], "2.3 2.3 5.0": ["thiazolides"], "9.0 4.4 19.3": ["hilum"], "2.1 4.9 16.2": ["kanang"], "9.6 10.0 31.1": ["sasanqua"], "7.4 -2.6 6.6": ["unrelease"], "5.5 6.6 9.6": ["medidas"], "14.3 9.5 16.5": ["gurgly"], "8.2 4.6 13.7": ["theannual"], "-4.1 6.3 6.6": ["indier"], "1.1 8.6 6.8": ["serpin"], "4.8 21.0 10.6": ["unvaryingly"], "5.5 13.8 0.4": ["icehockey"], "8.9 4.2 10.6": ["kitenge"], "11.8 9.2 3.7": ["suposedly"], "23.2 -1.8 15.6": ["southcoast"], "6.5 8.3 13.0": ["lucia"], "12.3 -5.4 25.4": ["atkins"], "-5.0 -1.4 -1.0": ["odp"], "8.5 -1.7 11.5": ["processeur"], "15.8 10.3 38.2": ["spincast"], "8.6 3.1 18.5": ["diphacinone"], "2.5 7.4 8.7": ["chopra"], "8.5 -1.3 15.4": ["restraunts"], "2.8 2.0 17.0": ["tulad"], "-0.4 1.2 11.7": ["perioral"], "10.4 16.6 7.7": ["defangs"], "4.5 11.8 2.4": ["ototoxic"], "3.0 0.2 10.5": ["annee"], "9.7 6.6 11.7": ["fcasts"], "10.5 15.0 7.2": ["sarkozy"], "0.8 1.5 11.0": ["llawn"], "20.1 21.2 26.1": ["heartsong"], "15.6 0.3 15.6": ["woodpulp"], "19.5 2.4 12.2": ["stox"], "-0.5 13.1 8.6": ["overdrink"], "16.6 0.2 12.1": ["retailtainment"], "15.4 24.2 8.7": ["weilds"], "3.3 3.3 9.4": ["fermentum"], "9.3 3.8 14.9": ["wull"], "7.7 6.3 11.4": ["heet"], "2.9 10.8 25.0": ["hama"], "5.3 0.4 -0.7": ["erd"], "19.5 10.6 2.1": ["nanorobot"], "-3.2 5.6 3.3": ["vcard"], "5.5 -0.1 10.1": ["orto"], "4.4 9.0 11.0": ["peralkaline"], "6.9 3.2 1.9": ["dcs"], "2.3 5.0 6.4": ["rockford"], "7.1 12.7 7.8": ["bayesian"], "-1.1 7.5 9.4": ["cource"], "13.0 8.1 11.2": ["gmo"], "8.1 16.8 16.0": ["photosystems"], "7.2 11.2 5.2": ["energisation"], "-0.1 3.2 -7.4": ["priciple"], "23.4 10.0 12.7": ["wibbly"], "11.4 27.3 15.9": ["defenselessly"], "14.5 12.3 21.6": ["awright"], "-1.7 5.8 3.3": ["splenectomized"], "-5.0 2.1 6.0": ["dyslipidemic"], "6.5 15.7 7.1": ["assimilations"], "5.4 7.5 16.3": ["agricutural"], "-0.3 4.0 -1.6": ["infrarenal"], "5.8 14.5 14.8": ["buffness"], "0.3 17.6 10.8": ["nucleophilic"], "6.1 3.0 8.9": ["lateralisation"], "20.5 3.9 8.4": ["mpta"], "-2.5 -6.5 -4.1": ["outdelivering"], "-1.4 8.1 16.7": ["hydrosol"], "-11.8 17.1 1.3": ["excursus"], "-1.6 10.1 15.0": ["iko"], "28.4 15.6 29.5": ["spearlike"], "10.2 2.3 14.3": ["beadmaking"], "2.6 -5.5 -0.3": ["osteobiologic"], "17.0 16.0 15.0": ["unbarred"], "0.1 5.6 9.2": ["nitroxyl"], "13.5 1.4 4.4": ["sust"], "11.6 11.2 16.0": ["okie"], "12.8 9.5 1.6": ["stereoviews"], "0.7 2.4 6.3": ["accelerando"], "11.1 10.5 3.8": ["trouping"], "4.5 1.7 1.1": ["spectroradiometer"], "27.5 18.8 14.3": ["superlaser"], "2.7 -3.3 0.5": ["funciones"], "4.8 18.3 7.1": ["spred"], "-0.3 8.9 15.0": ["lumaban"], "5.5 16.0 3.6": ["philantrophy"], "13.2 2.5 7.7": ["twentyish"], "4.1 5.0 14.2": ["butas"], "5.5 21.1 10.5": ["fugazy"], "14.0 23.7 15.1": ["henchwomen"], "3.1 8.1 14.5": ["ecletic"], "12.8 9.1 5.6": ["multidrive"], "8.9 11.1 11.6": ["megatasking"], "10.3 -13.6 8.0": ["nonbid"], "-8.0 -0.1 3.6": ["akademi"], "-9.2 -1.8 6.8": ["teleworked"], "6.2 8.5 5.3": ["natya"], "14.1 4.5 19.8": ["boatneck"], "-6.9 -4.7 -3.3": ["sga"], "1.4 -4.3 0.4": ["regul"], "2.1 3.2 10.2": ["humein"], "3.3 0.6 10.3": ["llywodraeth"], "9.7 3.9 21.1": ["swathers"], "14.6 13.1 5.7": ["ventillation"], "6.1 -4.9 12.8": ["hac"], "3.9 -6.4 5.0": ["creditcards"], "2.7 23.3 14.1": ["matchet"], "9.6 4.2 10.4": ["qiang"], "8.2 16.8 6.1": ["companyand"], "5.0 4.5 24.2": ["bocadillos"], "17.3 9.6 8.9": ["themin"], "11.2 5.0 22.6": ["batta"], "15.6 -3.1 7.5": ["schem"], "9.9 11.4 8.9": ["beatmania"], "2.5 4.1 7.7": ["educa"], "-1.5 6.9 8.6": ["bidaai"], "8.9 18.2 3.3": ["mdc"], "6.9 -3.1 1.7": ["restricciones"], "10.7 1.0 4.4": ["aainst"], "16.5 6.8 11.1": ["bombo"], "9.7 7.6 8.0": ["striate"], "2.5 21.9 5.3": ["transnationalists"], "0.6 3.8 2.0": ["presient"], "1.7 3.7 19.7": ["fluxed"], "6.7 7.3 8.3": ["clima"], "10.1 23.9 10.0": ["recriminating"], "8.9 4.4 9.5": ["sses"], "13.0 15.6 10.8": ["visaged"], "15.6 4.0 23.4": ["suga"], "-3.1 -0.9 6.6": ["retimer"], "-10.1 -4.9 -0.5": ["scholorship"], "12.5 14.2 8.1": ["nonterrorism"], "5.6 15.5 8.3": ["warmheartedness"], "6.9 3.1 1.4": ["aboutface"], "-7.7 3.8 3.4": ["nonacademics"], "10.5 11.2 20.2": ["alguien"], "15.0 7.8 17.4": ["bejewel"], "5.3 26.0 9.9": ["ungood"], "-0.0 6.3 8.1": ["streptozotocin"], "6.4 20.3 9.7": ["dand"], "32.0 23.3 16.4": ["buglike"], "7.1 8.4 25.3": ["dendrobiums"], "19.8 1.4 12.6": ["predigital"], "16.9 4.1 22.0": ["horti"], "2.7 4.0 2.9": ["arachnoiditis"], "4.5 7.7 11.6": ["amk"], "16.3 -4.6 12.7": ["peeptoe"], "3.2 15.9 12.5": ["matha"], "11.0 14.0 8.2": ["repoters"], "18.8 7.1 23.5": ["naranja"], "3.9 7.7 12.5": ["micronization"], "15.1 8.8 10.5": ["rebelde"], "0.5 3.5 6.1": ["victo"], "3.1 14.2 9.3": ["nole"], "8.0 14.4 26.6": ["bleachings"], "14.5 5.8 9.1": ["aneroid"], "1.4 31.1 1.6": ["deterrance"], "10.8 14.9 19.1": ["everyguy"], "8.6 8.9 10.3": ["adipokine"], "3.4 8.2 17.3": ["drunky"], "4.3 7.3 15.6": ["trin"], "9.0 5.1 6.0": ["idx"], "11.0 5.5 8.9": ["esperar"], "14.5 15.0 18.1": ["chinamen"], "15.7 11.5 10.1": ["mundus"], "0.6 10.9 1.0": ["simming"], "8.3 13.4 23.2": ["nosema"], "10.2 26.3 12.1": ["roundheads"], "8.4 11.0 8.5": ["playof"], "11.5 22.1 9.3": ["attitudinizing"], "10.7 11.8 18.9": ["sailable"], "5.7 4.6 9.5": ["nonchain"], "-2.6 7.6 9.3": ["telle"], "2.8 5.2 4.7": ["hydle"], "18.1 40.1 11.8": ["hoplites"], "4.9 8.4 11.2": ["hita"], "8.6 3.8 6.3": ["pnp"], "-7.5 -7.7 2.8": ["ential"], "5.3 -5.6 -4.1": ["organiz"], "2.5 0.0 20.9": ["dorset"], "-3.1 4.0 10.0": ["predisaster"], "15.7 17.3 18.0": ["nilly"], "-6.4 3.4 -0.9": ["hyperacute"], "7.7 4.5 2.3": ["prolongued"], "13.4 9.6 20.7": ["aconites"], "2.8 14.3 9.5": ["prostyle"], "1.7 5.1 10.5": ["ofo"], "6.4 5.3 -1.0": ["anticircumvention"], "2.4 1.9 -1.2": ["demarc"], "6.9 13.0 15.7": ["legcutter"], "1.1 3.9 11.3": ["chwarae"], "7.8 4.0 16.8": ["aventurine"], "6.6 5.5 8.8": ["lyrist"], "3.1 6.7 21.4": ["magsasaka"], "-5.8 -0.5 -4.0": ["memebership"], "-6.0 11.1 2.9": ["zade"], "19.3 -5.7 -0.2": ["cmpany"], "-1.5 17.2 10.7": ["personating"], "3.2 16.8 15.4": ["eructation"], "3.9 10.0 -1.4": ["referers"], "2.6 8.6 7.5": ["horner"], "11.7 14.6 23.2": ["mikoshi"], "11.3 19.4 11.6": ["meny"], "0.1 9.9 10.4": ["spectroscopists"], "12.6 10.4 13.1": ["erging"], "1.3 14.5 8.8": ["drawish"], "18.1 14.9 29.8": ["fernlike"], "0.4 9.6 8.1": ["governership"], "13.0 24.9 23.3": ["heebie"], "1.9 13.6 11.0": ["diseas"], "3.1 5.1 8.6": ["aper"], "6.8 3.7 13.6": ["gigatonne"], "15.5 22.0 21.1": ["tumblehome"], "16.7 4.9 9.4": ["nonmobile"], "1.5 10.7 19.5": ["kerajaan"], "4.1 -1.0 8.5": ["railpasses"], "-0.1 -5.5 -1.3": ["distribu"], "10.7 29.1 9.8": ["bioagent"], "-1.1 1.7 1.2": ["lettre"], "11.4 18.5 6.1": ["misallocates"], "-1.7 11.8 2.2": ["lactis"], "5.6 20.1 5.9": ["nondangerous"], "15.1 6.4 16.6": ["pachycephalosaurs"], "0.2 9.2 12.5": ["guni"], "9.6 1.9 9.0": ["doorslammer"], "9.3 5.2 15.4": ["dess"], "7.5 19.7 4.8": ["enviromentally"], "17.6 19.2 14.0": ["squeeky"], "7.9 25.8 17.5": ["sychophants"], "7.2 4.3 21.5": ["mott"], "6.0 4.1 13.1": ["andcan"], "5.0 4.9 -4.1": ["coversheet"], "6.7 15.5 22.0": ["endosymbiont"], "5.4 12.7 -1.6": ["nonrechargeable"], "-3.3 5.9 1.3": ["rewords"], "8.3 9.1 10.6": ["oldy"], "2.5 4.1 10.7": ["novia"], "3.2 18.2 6.4": ["barefacedly"], "6.8 5.1 18.7": ["kalyana"], "-2.8 4.4 2.4": ["lymphangioleiomyomatosis"], "2.0 11.2 12.4": ["doublecortin"], "-1.6 17.9 10.6": ["dslr"], "12.5 25.6 25.7": ["kraits"], "-9.3 7.9 1.9": ["demultiplexers"], "10.3 8.6 24.7": ["munchables"], "3.5 5.1 8.9": ["climatique"], "8.9 6.2 6.1": ["documentarylike"], "6.9 9.2 13.1": ["fourthplace"], "8.6 8.9 8.4": ["trp"], "2.8 8.0 19.7": ["nararamdaman"], "7.4 12.8 16.6": ["biosystem"], "2.4 9.0 13.2": ["mourir"], "-2.6 9.7 -0.5": ["dede"], "12.4 9.1 7.3": ["stronge"], "21.6 -0.0 -3.8": ["storecard"], "20.1 28.0 15.2": ["foreswears"], "-2.1 8.1 4.0": ["pressur"], "-6.0 -2.2 3.0": ["druh"], "14.1 31.5 2.9": ["overflies"], "2.8 11.7 13.6": ["crystallins"], "5.2 -1.8 9.8": ["kyr"], "-0.8 6.8 7.5": ["altace"], "8.5 4.9 11.0": ["airdam"], "23.9 13.0 40.9": ["fishsticks"], "7.3 5.1 8.6": ["cosmogenic"], "3.2 -1.4 6.9": ["healthclub"], "-5.0 1.2 9.7": ["hyponatremic"], "-4.5 10.6 7.3": ["rinpoche"], "-1.2 -2.7 11.6": ["nanoamps"], "2.6 14.5 6.4": ["pashed"], "-0.9 2.6 50.3": ["onaga"], "-2.1 15.6 11.7": ["nonjurisdictional"], "8.9 15.1 11.9": ["huuuuuge"], "-13.4 0.8 5.2": ["embolizations"], "1.9 5.8 -0.8": ["tachyarrhythmias"], "11.8 -2.5 -1.8": ["amarket"], "6.0 17.7 9.9": ["mayhaps"], "5.5 -1.0 9.8": ["calcipotriene"], "9.7 15.0 9.7": ["heavey"], "16.0 9.5 9.1": ["circumlunar"], "0.2 4.1 9.9": ["quantile"], "4.2 22.0 14.0": ["abzymes"], "-7.7 8.1 1.6": ["fmaily"], "4.0 3.1 13.4": ["maintindihan"], "-1.2 1.2 7.2": ["ocs"], "7.9 3.7 2.4": ["lumiliximab"], "19.4 9.4 14.8": ["murdoch"], "9.3 5.3 7.7": ["benzenes"], "11.5 -2.4 1.2": ["visbreaker"], "5.8 7.1 8.2": ["homeobox"], "-2.6 -0.6 2.9": ["cumes"], "17.2 6.3 15.8": ["airfreighting"], "6.9 9.3 14.0": ["minas"], "9.0 0.7 4.9": ["allyl"], "17.6 17.2 45.6": ["bronzeback"], "6.1 2.4 14.6": ["settimana"], "3.9 12.0 5.0": ["oppoents"], "11.1 9.5 7.7": ["reclusively"], "6.0 2.9 13.2": ["milliampere"], "23.9 -2.7 17.6": ["foodhall"], "11.8 -6.5 3.1": ["restauration"], "-3.8 11.6 5.4": ["cicumstances"], "15.7 6.1 9.4": ["scriber"], "13.8 -0.4 8.0": ["customhouse"], "9.5 -1.6 6.4": ["chlor"], "7.7 -6.3 10.1": ["sele"], "-0.1 24.9 8.3": ["lieutentant"], "18.9 21.0 16.1": ["reticules"], "3.0 23.3 12.9": ["athorities"], "4.9 3.0 14.0": ["hyperuricaemia"], "-1.4 4.0 3.6": ["anglican"], "7.7 11.1 15.0": ["hizzy"], "19.9 9.2 24.7": ["twizzlers"], "0.7 -5.4 0.9": ["psychobiologist"], "13.0 17.9 16.4": ["flambeaux"], "9.2 8.2 16.0": ["helically"], "14.1 3.2 17.1": ["conchos"], "7.2 0.5 12.7": ["rhan"], "8.3 3.3 14.4": ["thah"], "19.9 9.2 29.3": ["maidenhair"], "5.2 5.1 17.8": ["dizzle"], "13.0 19.4 11.2": ["unmaintainable"], "12.0 -2.8 15.0": ["imprintable"], "12.3 6.6 31.1": ["eggstravaganza"], "14.4 13.4 20.8": ["phylogeographic"], "10.1 39.4 3.3": ["guerrila"], "9.1 4.5 12.6": ["hermes"], "7.9 16.6 20.2": ["neccessities"], "-0.8 1.4 7.2": ["sandhya"], "4.9 8.3 17.7": ["cockapoos"], "16.3 4.2 -0.1": ["quity"], "8.6 4.6 -0.4": ["ultralightweight"], "8.0 -3.5 15.0": ["cabel"], "6.0 8.7 9.1": ["prayerwalking"], "-3.2 8.4 9.4": ["gopal"], "-10.5 8.0 1.7": ["decisors"], "16.3 13.4 20.4": ["nocks"], "8.8 7.4 6.9": ["thesouthern"], "2.7 7.2 14.3": ["intrasession"], "6.6 1.7 16.4": ["ritmo"], "15.9 22.6 6.8": ["strikeforces"], "12.3 11.9 8.1": ["hemorraging"], "2.5 3.9 8.9": ["coprocessing"], "12.0 -0.6 7.3": ["disulphide"], "0.9 -12.5 -3.0": ["coursepack"], "7.6 14.3 3.2": ["undersupported"], "16.6 10.9 36.3": ["braciola"], "14.3 4.6 9.4": ["abover"], "9.3 11.5 23.3": ["cannabutter"], "-0.8 14.4 2.6": ["politologist"], "16.7 3.5 18.5": ["gessoed"], "1.8 23.3 3.5": ["conflit"], "10.6 19.0 21.4": ["discolours"], "18.8 13.1 36.5": ["konnyaku"], "4.9 10.7 12.7": ["sphericity"], "4.8 -8.6 -3.2": ["zahn"], "6.1 24.8 -2.6": ["fanatism"], "0.9 7.2 3.8": ["orthopoxvirus"], "5.7 14.9 10.3": ["photic"], "7.4 14.5 21.1": ["scrumping"], "3.5 8.5 11.3": ["nonmelanoma"], "13.2 2.0 8.4": ["midperformance"], "-1.0 8.0 4.7": ["kuwa"], "7.6 -7.6 9.2": ["fondos"], "6.4 1.7 10.3": ["patrimoine"], "20.1 12.8 11.6": ["frauleins"], "14.3 8.9 10.1": ["hasto"], "7.8 13.0 14.4": ["headfake"], "2.5 4.7 13.0": ["jaisi"], "1.2 -5.2 1.0": ["aparece"], "5.9 3.0 14.3": ["hemangiosarcoma"], "2.1 10.5 15.5": ["ufl"], "10.2 6.4 7.3": ["acteur"], "18.1 14.7 12.7": ["fitball"], "-0.7 15.6 10.4": ["downticket"], "8.9 10.6 15.7": ["pulldowns"], "11.9 0.6 20.1": ["doce"], "-0.3 10.0 3.0": ["wasarrested"], "-6.7 7.9 4.8": ["threre"], "11.1 3.6 14.0": ["mercurochrome"], "3.2 14.8 3.6": ["mutilators"], "-4.9 8.2 -6.0": ["directoral"], "7.7 10.7 -0.2": ["murthy"], "9.1 10.3 8.2": ["diagraming"], "0.5 9.6 9.6": ["stimp"], "-4.2 2.1 -2.6": ["utions"], "4.6 9.7 5.6": ["runmaker"], "9.5 -2.6 5.1": ["howies"], "5.1 7.3 7.7": ["smriti"], "14.2 2.7 7.5": ["financialmarkets"], "19.5 12.6 15.8": ["ratter"], "3.1 7.9 7.4": ["anabolism"], "7.1 6.7 10.9": ["istockphoto"], "6.8 -1.0 8.4": ["seguito"], "5.1 8.9 5.8": ["ghosh"], "11.2 5.0 25.4": ["dubbel"], "13.3 5.6 21.2": ["miel"], "11.3 5.7 13.1": ["housebuying"], "0.4 -0.7 11.1": ["brahmi"], "1.8 -1.5 11.2": ["anarkali"], "18.7 0.8 -6.4": ["googlemail"], "-3.7 8.8 3.2": ["lymphocytosis"], "11.9 4.3 12.0": ["candombe"], "-4.4 1.7 5.5": ["obtention"], "2.7 1.1 7.7": ["uur"], "-3.3 11.8 -5.6": ["cliam"], "12.4 2.4 17.6": ["salers"], "12.0 9.4 5.1": ["mutualise"], "9.5 -3.8 6.6": ["andoperating"], "-0.1 6.6 1.2": ["ultimatetv"], "-1.8 -0.5 0.5": ["sonra"], "12.3 8.9 14.2": ["parasiticide"], "6.8 7.6 19.4": ["topdress"], "7.6 -2.6 12.9": ["vertu"], "10.3 19.2 11.7": ["rekha"], "15.8 10.1 34.2": ["arrabbiata"], "8.3 20.1 31.2": ["katipo"], "-0.6 -5.0 -10.4": ["mnister"], "17.9 13.0 20.2": ["longdaysin"], "4.8 14.0 12.3": ["synonymy"], "6.0 10.9 4.8": ["sketchwriter"], "10.0 2.3 8.2": ["parisian"], "10.3 4.8 11.1": ["udp"], "0.0 7.8 8.8": ["contraire"], "6.0 6.0 11.7": ["commodo"], "14.9 -7.6 4.7": ["shareout"], "-3.0 -1.9 3.6": ["acidemia"], "6.7 4.7 9.2": ["tiempos"], "3.1 6.8 11.8": ["happpy"], "1.6 7.8 -0.2": ["explique"], "4.9 6.3 8.2": ["tablespaces"], "12.6 0.4 -2.5": ["presso"], "11.6 10.1 8.6": ["monochromators"], "8.1 11.4 23.9": ["lahmacun"], "4.7 -8.2 7.1": ["syth"], "14.9 12.9 10.7": ["omb"], "9.8 5.3 18.4": ["belmont"], "14.4 8.7 14.5": ["eated"], "8.2 20.8 18.9": ["unfavorite"], "-1.8 6.2 18.3": ["apat"], "13.1 13.7 13.2": ["porkbarrel"], "-0.2 4.5 6.8": ["permanganate"], "13.1 6.9 17.9": ["zapateado"], "2.1 4.5 6.2": ["commenti"], "13.0 4.4 7.6": ["elimi"], "11.3 4.0 4.7": ["riggs"], "12.0 6.8 0.4": ["belike"], "6.9 -6.1 9.6": ["mboepd"], "13.0 28.8 14.6": ["matchlock"], "-3.5 8.5 12.9": ["bumpings"], "2.5 17.4 -2.6": ["rashtra"], "20.6 8.3 47.5": ["leatherjacket"], "2.1 12.6 3.1": ["sulha"], "0.4 4.2 6.0": ["peroxisomal"], "2.0 2.4 11.2": ["jawani"], "12.4 -12.9 0.0": ["bioindustrial"], "6.2 10.5 15.9": ["southwesternmost"], "5.1 12.4 4.6": ["zhurnal"], "5.0 1.7 6.0": ["orvisit"], "5.0 2.8 5.5": ["seres"], "14.8 3.0 4.6": ["disconnectors"], "7.6 6.3 16.3": ["flere"], "6.2 5.9 4.1": ["everygirl"], "6.3 10.5 -0.2": ["staunches"], "5.0 0.2 6.5": ["independiente"], "5.7 1.4 7.5": ["tweede"], "6.8 7.4 10.4": ["choos"], "10.2 16.5 9.6": ["villanous"], "-6.0 10.5 2.7": ["referenceability"], "12.2 7.6 17.4": ["puerta"], "-1.3 -0.9 5.2": ["aggrecan"], "-0.9 22.6 11.2": ["disreputably"], "9.9 9.6 12.4": ["motivo"], "11.9 4.3 5.8": ["wardrobed"], "11.6 0.4 14.4": ["ercise"], "2.4 2.4 7.4": ["natriuretic"], "6.3 4.9 10.8": ["alkalized"], "14.1 16.6 12.3": ["missi"], "-4.3 11.5 11.7": ["hadi"], "9.8 7.7 9.3": ["nanoelectromechanical"], "3.6 11.9 24.7": ["shasta"], "14.5 11.8 29.7": ["saddlebacks"], "18.3 2.8 5.7": ["nuvo"], "12.9 16.8 13.8": ["depressurizes"], "-3.3 7.8 5.2": ["alkylating"], "5.6 6.4 6.9": ["nonanal"], "21.3 12.7 22.2": ["nodder"], "4.5 7.6 12.1": ["vinden"], "4.3 19.7 7.0": ["citeh"], "22.2 11.7 6.4": ["unsolicted"], "2.2 8.9 10.1": ["bowdlerization"], "8.3 16.4 26.0": ["hatcher"], "1.0 3.4 17.4": ["buffa"], "12.6 20.0 10.6": ["exoplanetary"], "7.9 11.2 10.5": ["acciden"], "6.7 4.1 5.5": ["venomics"], "-0.6 16.6 9.8": ["bazi"], "3.7 3.2 16.8": ["pagi"], "3.1 8.3 12.7": ["underwood"], "0.9 10.3 11.1": ["ipsec"], "9.4 4.7 24.7": ["spineflower"], "-1.3 9.7 13.5": ["coachers"], "11.6 3.5 14.9": ["donar"], "-2.4 6.6 7.0": ["serializers"], "1.5 17.1 8.8": ["bhumi"], "11.0 16.3 12.8": ["roadracers"], "4.3 -2.4 1.9": ["researchand"], "14.3 17.2 19.3": ["sunstone"], "-1.1 6.7 1.0": ["unclonable"], "7.2 10.0 1.4": ["criminial"], "-2.2 -5.3 10.3": ["fininshed"], "-6.5 3.6 2.8": ["appre"], "7.8 10.3 15.1": ["raintree"], "1.8 1.1 -1.4": ["irms"], "0.8 -1.7 13.7": ["pagdating"], "-4.2 19.2 2.0": ["anbody"], "19.1 11.3 14.5": ["viruslike"], "14.3 25.3 0.9": ["uninvent"], "25.1 16.2 23.7": ["mancala"], "0.2 3.9 14.0": ["klase"], "8.3 8.0 4.9": ["jure"], "11.0 21.3 14.6": ["dumm"], "17.6 14.3 2.3": ["embracer"], "2.3 17.6 4.0": ["tacts"], "17.1 8.0 11.6": ["spankingly"], "3.4 0.3 1.9": ["decriminalises"], "16.5 14.7 19.6": ["chimplike"], "2.8 0.4 8.4": ["mese"], "-1.7 10.3 6.5": ["paaji"], "17.1 12.9 13.0": ["flightsuit"], "-4.5 -1.2 4.1": ["endovenous"], "4.1 0.5 2.2": ["superclinic"], "3.6 3.5 -0.2": ["avai"], "12.0 8.7 8.6": ["microtissues"], "12.8 13.8 12.1": ["causeth"], "6.7 2.8 18.5": ["felly"], "-6.3 3.5 2.2": ["sympathomimetic"], "7.1 9.1 18.3": ["noncoastal"], "17.7 4.4 19.6": ["cocobolo"], "-3.8 4.2 9.3": ["oxime"], "14.9 -10.2 14.5": ["gaw"], "-5.3 10.7 1.9": ["middot"], "15.7 12.3 5.4": ["oids"], "10.2 13.4 7.9": ["stimuluses"], "6.3 5.4 7.1": ["cytometers"], "7.3 4.6 2.4": ["prominantly"], "4.5 12.4 14.9": ["canoodles"], "16.4 11.4 22.7": ["challis"], "9.2 12.0 6.7": ["porus"], "7.5 8.6 17.5": ["kirsten"], "14.0 1.7 13.9": ["gaylord"], "12.6 5.4 2.5": ["watchs"], "4.5 5.8 25.3": ["lomilomi"], "9.8 -4.0 10.4": ["hyaluronic"], "4.9 14.7 28.8": ["uncoloured"], "8.6 3.2 15.7": ["macules"], "13.9 10.0 4.2": ["debis"], "1.3 4.4 11.2": ["setshaba"], "9.4 4.5 10.7": ["pasada"], "-16.2 16.3 -3.6": ["augmentee"], "7.2 21.0 8.8": ["patriarchies"], "5.7 -7.9 -2.5": ["fournit"], "12.4 16.4 15.7": ["vatos"], "8.7 -0.9 6.0": ["lebrity"], "8.1 5.3 11.9": ["celle"], "-7.2 11.8 10.4": ["ibadat"], "7.8 4.3 27.9": ["langka"], "4.2 -3.5 -4.8": ["isee"], "17.3 4.1 28.0": ["verbenone"], "8.2 12.0 13.1": ["ferricoxide"], "12.0 16.2 9.8": ["andmake"], "-5.5 20.2 9.6": ["threevway"], "-0.4 13.6 9.4": ["centration"], "-3.1 9.9 4.8": ["asphyxial"], "3.0 8.9 -4.3": ["revalation"], "8.1 4.7 22.4": ["spherification"], "11.0 1.4 0.3": ["commerial"], "21.6 21.1 16.8": ["beginings"], "-7.6 -7.3 10.1": ["itor"], "2.9 -0.1 11.6": ["increaseof"], "-1.4 4.5 15.3": ["lungo"], "14.0 3.6 12.0": ["tuaminoheptane"], "-9.1 3.0 8.4": ["deoxynivalenol"], "1.8 3.3 10.8": ["jantri"], "8.2 15.7 15.7": ["telemeter"], "9.0 4.4 -2.5": ["fffho"], "5.9 10.7 16.2": ["blahblah"], "6.9 -4.3 14.7": ["diwethaf"], "6.6 5.7 12.3": ["campos"], "3.9 6.9 16.8": ["koothu"], "28.1 6.2 9.5": ["micra"], "10.4 19.8 -2.6": ["depolarize"], "5.2 6.6 7.2": ["centrespread"], "10.0 -7.0 -0.1": ["partenaire"], "7.9 8.0 29.6": ["daging"], "6.5 -3.2 -1.5": ["suchs"], "15.8 8.3 28.4": ["truckbed"], "9.5 18.0 7.0": ["codifier"], "7.6 17.6 15.0": ["eastwest"], "15.8 -0.1 11.5": ["juegos"], "0.5 21.8 11.5": ["inclosed"], "18.5 6.6 10.5": ["rethemed"], "10.8 10.6 9.2": ["ecollective"], "1.9 15.3 19.0": ["rhizoctonia"], "2.3 4.6 10.0": ["multiperil"], "11.6 4.1 2.7": ["flatrates"], "17.4 4.3 37.1": ["witlof"], "0.3 13.4 5.4": ["bioptic"], "-1.0 13.5 7.4": ["intracavity"], "4.6 14.3 19.5": ["tenter"], "3.5 11.4 9.9": ["capitano"], "-3.2 9.5 9.4": ["tese"], "4.6 4.6 40.4": ["wantons"], "-2.1 -0.9 -4.1": ["kampala"], "15.8 8.9 12.2": ["bovver"], "3.6 9.2 -1.1": ["butyrylcholinesterase"], "10.7 0.3 25.8": ["vieja"], "-1.8 8.9 10.3": ["harmon"], "-2.6 15.3 10.1": ["inferable"], "-3.1 0.1 7.0": ["domi"], "25.7 13.6 18.9": ["climbin"], "4.1 26.8 8.6": ["despicableness"], "4.1 10.4 8.7": ["powersupply"], "6.5 22.9 3.2": ["ayn"], "6.9 11.5 4.5": ["shapeable"], "8.7 1.9 -5.7": ["furthe"], "-8.5 -5.9 6.3": ["crackerbarrel"], "-0.3 10.0 5.0": ["foud"], "13.3 13.2 8.8": ["tilings"], "18.0 9.7 8.3": ["smashings"], "5.4 -0.1 4.1": ["appareils"], "28.2 18.1 11.9": ["mechanoid"], "8.1 19.6 11.2": ["synesthete"], "14.0 8.6 18.1": ["skeletally"], "8.1 6.1 30.7": ["boti"], "2.0 7.5 2.2": ["regurgitant"], "15.8 14.8 10.2": ["extradimensional"], "17.1 18.3 9.2": ["astra"], "1.0 8.8 -5.9": ["miniser"], "2.9 3.4 5.2": ["saludo"], "6.5 17.4 16.4": ["haint"], "13.5 18.7 13.3": ["mysterium"], "10.8 0.7 11.9": ["sopranino"], "6.6 6.4 13.6": ["staffordshire"], "10.4 5.6 6.1": ["puisque"], "1.7 11.5 12.4": ["laxman"], "-0.3 6.7 23.5": ["beachwater"], "9.7 -4.4 12.9": ["swyddi"], "19.9 14.2 16.0": ["clodhopping"], "14.5 16.6 5.0": ["textarea"], "5.9 10.3 2.5": ["bipropellant"], "16.2 -0.7 0.1": ["perating"], "4.1 7.4 16.7": ["solani"], "-4.7 15.9 1.2": ["endoleak"], "5.5 -4.1 -4.8": ["instiutions"], "6.0 8.7 10.2": ["rous"], "20.2 10.0 15.5": ["boinging"], "12.5 10.3 21.5": ["waitron"], "-2.5 -3.4 1.9": ["noncompulsory"], "-0.5 3.7 0.3": ["overlines"], "7.4 9.3 14.3": ["bromo"], "-5.0 6.2 5.6": ["polyarticular"], "4.3 3.7 11.9": ["prepardness"], "14.0 10.9 27.3": ["headstay"], "8.1 14.8 17.6": ["apachekid"], "4.0 2.9 5.4": ["ugrade"], "14.2 0.1 3.5": ["systeem"], "13.1 8.2 23.2": ["deutzia"], "-4.0 -7.9 10.7": ["westchester"], "4.9 16.8 16.6": ["wabi"], "6.5 2.1 2.4": ["mds"], "-8.1 1.4 0.4": ["marzes"], "12.9 7.3 11.8": ["ptg"], "6.1 1.4 12.2": ["gravida"], "5.1 1.9 12.2": ["prueba"], "4.2 5.7 7.6": ["velocidad"], "3.1 3.2 6.9": ["myxoid"], "5.0 27.4 14.9": ["gevaar"], "15.4 0.7 11.2": ["caryard"], "8.6 27.3 1.9": ["exaggerators"], "8.8 -0.3 6.1": ["frontals"], "12.8 3.9 14.4": ["fluorapatite"], "21.1 6.3 16.7": ["tasmanian"], "4.1 5.3 9.0": ["jugador"], "2.4 5.1 3.5": ["sonero"], "4.8 3.7 19.4": ["leone"], "-4.8 -2.5 8.2": ["iamba"], "4.9 9.8 7.5": ["portant"], "11.2 10.2 5.1": ["stereoscopically"], "10.5 3.8 14.3": ["biocontainers"], "13.0 15.0 1.3": ["semaphoring"], "4.4 3.8 10.1": ["ballades"], "19.4 8.6 13.2": ["biohybrid"], "2.1 0.5 3.5": ["managem"], "-1.5 0.7 17.3": ["kongresista"], "-4.2 17.8 5.8": ["nonmonogamous"], "7.5 28.1 12.5": ["pedos"], "3.0 -0.5 -0.2": ["obtenu"], "19.1 16.7 25.2": ["lifevests"], "9.3 12.1 19.1": ["reproductivity"], "10.5 4.3 2.8": ["llevar"], "8.4 33.1 3.9": ["militas"], "1.1 11.5 10.2": ["pronator"], "5.8 -0.3 17.9": ["aquacise"], "8.5 24.7 10.5": ["gunwoman"], "1.5 11.5 5.7": ["adouble"], "6.7 1.8 1.9": ["superduo"], "-3.7 15.5 0.4": ["opionions"], "26.0 18.3 39.1": ["flensing"], "6.5 10.7 5.5": ["computerese"], "2.1 15.1 12.4": ["congradulations"], "14.5 9.5 4.7": ["unaffectionately"], "16.7 10.2 14.5": ["blasthole"], "7.0 20.1 3.8": ["autoland"], "14.0 19.9 16.2": ["farer"], "8.9 9.5 10.5": ["shorfall"], "-0.4 7.6 10.1": ["bimanual"], "0.9 16.0 10.9": ["kaala"], "18.4 11.0 32.9": ["caribous"], "6.3 -3.5 1.5": ["immobilier"], "7.6 -1.7 1.6": ["permet"], "10.7 11.5 6.0": ["texan"], "1.0 7.5 -1.1": ["prelitigation"], "4.0 -0.5 1.9": ["fullsome"], "3.0 5.8 15.6": ["toxicologies"], "2.8 1.2 6.3": ["geobiologist"], "5.5 -4.8 6.1": ["titoli"], "2.4 10.1 5.9": ["lacrimation"], "2.3 11.4 15.2": ["salicylic"], "-0.4 0.1 6.0": ["outcoupling"], "15.9 8.9 15.6": ["gopurams"], "9.9 13.6 17.9": ["caners"], "8.5 -4.0 14.5": ["kuruvai"], "9.0 9.7 12.3": ["sloooooow"], "-8.1 -6.7 6.7": ["rett"], "5.4 -1.4 9.4": ["nise"], "17.2 19.4 20.8": ["pouters"], "10.8 5.0 16.1": ["huipiles"], "17.2 5.7 40.2": ["prata"], "-0.7 0.9 8.0": ["zwar"], "-3.6 6.9 5.3": ["mineralocorticoid"], "5.4 4.2 10.8": ["plainspokenness"], "14.3 -1.6 6.3": ["pilotes"], "12.9 4.1 4.4": ["ecuador"], "11.4 1.7 11.9": ["orning"], "3.3 2.0 2.1": ["delived"], "20.3 1.4 12.5": ["cigarets"], "-12.1 6.2 -5.1": ["readministered"], "1.8 1.7 5.4": ["momagri"], "16.0 1.2 12.0": ["ballskirt"], "26.4 3.8 14.4": ["waterbottle"], "14.3 25.9 12.9": ["wondrousness"], "11.4 15.0 7.5": ["sines"], "17.7 0.2 41.2": ["amur"], "-0.0 4.8 8.7": ["safar"], "10.1 6.4 18.3": ["hipsterish"], "3.5 3.4 9.1": ["hexadecane"], "0.8 10.5 5.4": ["onclick"], "14.4 14.5 19.0": ["lavalava"], "1.5 -5.0 11.1": ["tically"], "-8.3 -0.9 -0.2": ["rios"], "10.9 0.1 2.0": ["biedt"], "23.3 2.7 4.6": ["trons"], "5.7 7.7 9.9": ["neurexins"], "0.2 2.6 7.6": ["phototransistors"], "-1.2 0.6 9.9": ["nitroprusside"], "9.0 4.3 3.8": ["multidonor"], "0.2 5.2 3.2": ["codeshared"], "9.5 27.7 10.5": ["shineth"], "1.1 15.0 0.4": ["idolator"], "12.0 3.4 4.4": ["microtechnologies"], "12.5 8.0 16.1": ["endomorph"], "2.5 -0.2 7.3": ["selenocysteine"], "4.0 23.0 7.2": ["elese"], "16.6 11.1 33.8": ["flowerets"], "15.2 3.1 32.2": ["lauki"], "11.5 5.6 8.5": ["accepter"], "4.7 -2.2 14.3": ["semitendinosus"], "9.2 12.0 13.1": ["lve"], "11.9 8.9 7.7": ["tableless"], "8.2 15.9 1.0": ["flapless"], "2.6 0.5 -0.3": ["organizaciones"], "1.3 6.2 15.6": ["phosmet"], "4.4 -0.2 2.9": ["initio"], "-4.1 1.7 4.7": ["seeen"], "-2.6 9.4 12.0": ["taumbayan"], "13.6 11.0 6.5": ["inci"], "1.3 8.8 5.3": ["arteriotomy"], "5.4 2.1 7.1": ["escuchar"], "-4.0 11.0 11.7": ["levin"], "22.4 -0.3 9.3": ["maufacturing"], "13.2 11.9 15.9": ["corniced"], "-4.2 -0.6 9.7": ["ngarm"], "16.4 0.7 12.8": ["backon"], "5.4 10.1 15.0": ["masabi"], "2.6 -2.8 9.3": ["droh"], "12.2 3.5 3.5": ["multicolumn"], "12.6 8.9 14.1": ["swaybars"], "-4.4 5.5 3.6": ["multirun"], "8.7 -2.0 -7.8": ["energetika"], "-3.7 19.3 6.1": ["dehabilitating"], "3.5 5.3 17.2": ["haere"], "8.7 2.7 16.1": ["rodded"], "4.2 2.1 14.3": ["speedboarding"], "9.1 4.1 8.8": ["reportely"], "8.5 25.2 8.4": ["misunderestimating"], "8.2 27.6 6.2": ["depravations"], "7.3 1.9 7.6": ["cyclosportive"], "0.9 5.8 7.7": ["brevets"], "8.2 7.9 8.4": ["nanobubble"], "4.4 -3.1 11.5": ["dydd"], "6.5 -8.0 1.1": ["armani"], "15.1 14.2 19.1": ["dekeing"], "6.2 9.8 12.6": ["replisome"], "-0.8 8.3 18.2": ["kaku"], "5.5 19.5 17.9": ["harts"], "-1.0 1.0 0.5": ["nosi"], "-1.3 10.2 14.4": ["lognormal"], "15.8 4.8 9.9": ["isotonics"], "4.6 8.6 10.7": ["vrat"], "12.5 15.9 21.0": ["overruffed"], "11.4 6.6 30.4": ["tiropita"], "8.4 10.1 5.0": ["fluidjet"], "7.2 17.9 10.6": ["palaeolithic"], "9.8 20.9 12.8": ["mydlink"], "2.8 8.9 7.8": ["acho"], "13.2 19.3 17.1": ["brusk"], "-0.4 14.6 1.9": ["indictement"], "0.1 20.6 8.5": ["kareem"], "3.7 2.1 5.8": ["viewsets"], "-8.8 17.5 3.4": ["lashon"], "7.1 5.7 26.6": ["bladderwrack"], "6.6 4.3 9.6": ["boingboing"], "-1.1 2.0 8.6": ["omental"], "-6.6 -7.9 -5.0": ["rted"], "8.5 9.3 19.6": ["kik"], "2.8 0.8 6.1": ["claudia"], "4.1 10.9 12.5": ["vulcanised"], "18.6 5.1 31.6": ["bengalensis"], "-4.8 12.3 11.6": ["halatuju"], "13.4 9.6 31.3": ["asphodel"], "6.7 -0.1 6.2": ["eventos"], "19.5 3.1 14.1": ["boofy"], "2.6 13.8 13.5": ["gand"], "20.4 10.8 9.2": ["klystron"], "5.0 4.4 5.5": ["underbridges"], "5.6 2.9 9.0": ["tonght"], "1.3 9.7 5.4": ["comfirm"], "6.4 3.3 10.9": ["troffer"], "22.1 17.0 15.3": ["unmatching"], "2.9 10.6 16.6": ["kayla"], "7.1 4.0 16.3": ["boke"], "14.7 5.6 53.4": ["opilio"], "3.3 -1.5 13.1": ["parehong"], "-5.5 0.6 22.9": ["baykeeper"], "14.9 -2.7 18.5": ["catechu"], "3.4 3.5 11.4": ["contri"], "0.0 4.9 6.3": ["athermal"], "10.9 9.6 14.1": ["thole"], "1.2 13.9 8.5": ["descendancy"], "8.1 8.9 16.0": ["brettanomyces"], "5.5 12.7 7.3": ["sool"], "5.9 13.5 5.3": ["vishnu"], "12.5 -2.0 10.0": ["treme"], "17.3 9.5 22.2": ["supertree"], "3.3 29.8 6.1": ["manouvers"], "7.6 -0.3 9.2": ["vcd"], "7.3 7.1 9.6": ["hotmelt"], "8.1 -6.8 6.3": ["subsciption"], "13.5 3.5 18.4": ["microphotography"], "13.7 4.6 10.4": ["dailymail"], "15.6 15.8 4.5": ["hios"], "-6.5 13.3 10.4": ["arteriolar"], "5.2 -0.3 14.0": ["requinto"], "0.1 -2.5 -1.8": ["fortepianist"], "-8.1 -2.2 -4.8": ["mylife"], "5.1 14.4 8.1": ["jcrasnick"], "9.8 21.0 7.0": ["expiatory"], "6.5 6.4 8.5": ["automall"], "-3.5 6.4 2.7": ["serodiscordant"], "6.6 4.7 14.6": ["convienence"], "20.3 15.2 17.2": ["spicule"], "1.7 0.6 18.1": ["tious"], "10.7 16.6 12.2": ["yuu"], "7.3 8.6 13.0": ["marri"], "9.4 17.9 2.4": ["narcostate"], "17.7 17.3 16.9": ["vulturous"], "7.7 -0.9 10.9": ["derbyn"], "16.4 8.2 22.4": ["coozie"], "0.0 23.7 14.0": ["denuclearised"], "15.6 11.6 22.2": ["fizzies"], "8.5 26.6 10.7": ["fearsomeness"], "10.5 -0.9 5.7": ["forground"], "11.9 6.0 12.8": ["alifetime"], "7.1 -1.1 12.5": ["sludgier"], "8.3 8.8 2.5": ["neurotheology"], "-0.2 11.2 0.1": ["delicts"], "22.8 11.5 20.8": ["fountaining"], "15.7 24.1 29.9": ["subantarctic"], "9.8 14.3 3.8": ["cybersleuths"], "-2.2 10.3 3.0": ["juma"], "4.3 7.0 6.9": ["logies"], "0.3 1.1 15.4": ["sweldo"], "5.9 13.3 6.7": ["pranic"], "7.8 15.8 10.8": ["superstring"], "-1.0 0.6 6.4": ["pancreaticoduodenectomy"], "-1.4 2.3 9.6": ["xoghol"], "4.2 12.8 2.3": ["distorter"], "5.1 15.8 4.3": ["cratic"], "-1.5 -11.2 3.1": ["iated"], "3.6 3.7 1.8": ["fateh"], "14.2 21.6 6.1": ["outdefended"], "6.1 9.1 9.5": ["joc"], "6.8 12.5 18.3": ["oti"], "-0.8 3.5 17.4": ["moyens"], "15.9 15.6 3.4": ["powere"], "-7.2 -4.4 -0.2": ["ffer"], "-2.8 -2.8 3.6": ["pentosan"], "18.9 3.5 5.4": ["andsolutions"], "16.3 6.9 7.8": ["extraordinaries"], "5.5 30.4 9.4": ["racialize"], "-9.4 2.6 -4.5": ["postvaccination"], "1.4 2.4 8.8": ["acylated"], "-1.4 14.3 -2.1": ["underminded"], "-0.6 11.5 15.5": ["irwin"], "5.6 -2.2 3.4": ["polycondensation"], "12.5 5.7 23.2": ["redish"], "13.1 21.0 12.9": ["jinni"], "7.4 4.9 -0.4": ["aretrademarks"], "1.0 2.4 4.4": ["lutheran"], "9.0 2.9 12.0": ["justgiving"], "20.4 14.9 19.6": ["resiny"], "2.9 12.3 7.5": ["unpartisan"], "13.4 8.6 27.6": ["breadlike"], "11.9 7.5 6.9": ["claime"], "-1.8 -0.4 8.4": ["caer"], "17.9 9.8 22.4": ["guenons"], "-5.9 16.0 10.4": ["mred"], "4.1 0.6 -3.9": ["epd"], "7.0 4.0 6.7": ["cfg"], "15.6 3.0 14.2": ["headhouse"], "12.8 15.9 22.7": ["dioica"], "3.5 -3.5 14.6": ["ddamwain"], "1.3 0.7 18.4": ["passa"], "-0.7 0.5 3.7": ["estuvo"], "9.9 2.4 9.0": ["mtoe"], "2.9 9.0 14.4": ["morir"], "20.7 0.8 15.9": ["flatspin"], "9.0 0.2 11.7": ["couterparts"], "10.7 9.4 4.6": ["nadine"], "10.3 14.9 30.6": ["mohua"], "-4.0 5.5 0.7": ["cervicitis"], "5.6 10.8 -3.9": ["monitering"], "12.4 9.1 19.0": ["sidestick"], "-3.1 -4.3 10.5": ["periurethral"], "10.3 0.9 7.5": ["excpected"], "15.0 -1.1 -1.5": ["convector"], "5.5 4.6 -6.4": ["yerar"], "3.6 2.8 13.8": ["kinuha"], "7.0 15.2 16.8": ["tressel"], "21.4 10.6 25.8": ["shoveller"], "12.4 9.0 39.7": ["luwak"], "0.6 2.7 -1.1": ["prosectuors"], "10.6 1.6 19.1": ["cellent"], "1.3 1.3 7.5": ["homebuy"], "1.7 1.9 2.9": ["mises"], "3.6 41.2 2.3": ["munafiq"], "3.3 9.2 2.7": ["talkradio"], "6.2 3.8 12.7": ["micronised"], "0.1 -0.5 3.7": ["linq"], "2.9 19.8 17.6": ["soilborne"], "3.8 13.3 9.9": ["scanlation"], "-1.4 -4.1 5.8": ["cliffe"], "20.8 9.1 22.0": ["coonskin"], "11.6 16.5 15.0": ["pelotons"], "9.9 14.2 17.3": ["manoj"], "2.6 27.5 2.0": ["aggresion"], "-0.3 11.0 5.7": ["dysmorphic"], "2.0 5.4 4.5": ["staffwriter"], "8.0 6.6 30.9": ["puerco"], "14.8 2.0 11.0": ["chondritic"], "5.6 13.5 13.9": ["tummler"], "-4.1 17.4 5.5": ["marjaa"], "11.8 3.2 13.7": ["workshirt"], "0.8 4.2 2.7": ["presolar"], "9.3 8.1 17.1": ["palacio"], "6.8 4.4 13.2": ["geven"], "17.4 1.2 9.5": ["unveling"], "5.2 1.7 5.4": ["proyecto"], "-1.6 2.5 11.0": ["demux"], "5.5 14.7 1.5": ["minar"], "8.4 13.2 12.3": ["highpressure"], "8.7 7.7 15.5": ["lugares"], "4.7 -1.8 2.0": ["audiologic"], "2.6 14.5 3.5": ["ribery"], "10.3 12.9 11.1": ["umbral"], "7.4 2.5 9.6": ["reenable"], "13.5 5.5 16.6": ["tokin"], "7.9 0.9 15.6": ["gramin"], "7.6 3.3 4.4": ["flavanoid"], "10.5 17.1 2.8": ["migr"], "4.6 16.3 19.6": ["jeezy"], "5.2 8.1 12.3": ["comhairle"], "19.8 10.9 3.6": ["downloadble"], "18.4 17.1 1.2": ["widebodied"], "-0.3 8.1 0.8": ["responsables"], "15.9 0.5 14.6": ["artisanry"], "4.0 2.7 10.8": ["sarasota"], "-6.4 3.2 -0.2": ["dessen"], "13.2 19.2 26.8": ["pimpernel"], "-0.2 -3.1 9.4": ["rountable"], "17.0 3.1 18.9": ["tles"], "-5.3 5.5 2.4": ["pragma"], "6.3 11.1 -3.2": ["provate"], "-1.5 5.1 10.0": ["hj"], "1.2 6.3 2.1": ["pleurodesis"], "-0.4 -4.7 13.0": ["holm"], "8.4 23.2 19.2": ["waaah"], "-6.2 10.2 3.5": ["dastaar"], "-2.9 6.3 8.3": ["katsina"], "2.1 15.8 7.7": ["heterochromatic"], "4.2 -0.1 2.8": ["organzing"], "9.9 17.4 1.0": ["arest"], "10.6 5.4 2.3": ["corium"], "-6.2 9.3 16.2": ["makaka"], "7.1 10.6 1.8": ["paperport"], "1.1 5.5 11.9": ["dhaka"], "13.9 12.4 13.3": ["frothers"], "17.9 0.3 10.0": ["attraverso"], "5.9 6.8 11.8": ["nader"], "13.7 16.0 12.9": ["netward"], "1.0 1.9 1.5": ["escritura"], "1.7 7.0 5.2": ["altro"], "21.2 10.7 13.5": ["regathers"], "-0.3 15.6 9.0": ["flirter"], "-3.3 14.2 7.9": ["culturable"], "3.1 11.9 -3.5": ["datastreams"], "-5.7 4.6 8.5": ["meaing"], "8.5 0.1 11.3": ["tbt"], "5.3 4.3 -2.1": ["therecord"], "2.2 12.7 5.0": ["jagran"], "6.7 4.4 20.1": ["cambial"], "-6.0 9.1 8.1": ["overcontribution"], "7.0 3.8 13.6": ["elisa"], "-3.4 -1.2 -1.0": ["meetingtrak"], "14.5 4.8 7.6": ["soure"], "19.4 9.1 16.6": ["turtleback"], "-1.4 12.3 1.6": ["crutial"], "4.0 5.3 22.5": ["ratoon"], "12.3 15.3 4.7": ["capacitative"], "-0.3 10.7 9.4": ["lobule"], "13.4 7.7 9.3": ["photobooths"], "17.8 24.6 13.4": ["tumbrils"], "6.7 4.2 10.6": ["experie"], "4.0 -2.9 10.8": ["centistoke"], "17.1 19.1 8.8": ["palely"], "19.0 8.9 24.0": ["walleted"], "24.1 -2.1 21.8": ["meltaways"], "4.6 4.6 10.6": ["macron"], "13.0 3.1 15.2": ["meatcutter"], "13.5 7.4 10.2": ["dehorn"], "-0.2 9.3 1.4": ["borane"], "5.3 6.5 12.4": ["gry"], "3.9 14.1 2.8": ["corespondents"], "25.0 1.4 48.2": ["rockhopper"], "17.0 2.3 37.1": ["galantine"], "11.4 4.5 6.4": ["gaita"], "6.1 8.5 18.4": ["melanocytic"], "7.7 11.4 18.5": ["sliped"], "-3.0 4.2 5.7": ["hydrolases"], "4.5 12.0 8.0": ["inexplicability"], "14.4 13.5 7.0": ["webbrowser"], "19.5 -0.2 20.2": ["brik"], "-1.0 6.0 19.9": ["pasahero"], "12.7 4.8 17.7": ["dualcore"], "5.4 19.1 15.6": ["mousepox"], "14.9 9.4 7.3": ["finmins"], "5.9 8.2 2.7": ["proveo"], "3.1 8.8 5.3": ["retreiving"], "5.6 9.3 20.5": ["saltern"], "-1.6 2.8 4.8": ["biol"], "8.9 8.6 23.5": ["odori"], "-11.4 1.6 -6.1": ["ested"], "-2.6 5.1 6.3": ["kehna"], "5.2 2.3 7.6": ["resea"], "6.1 14.4 4.0": ["speedgun"], "4.2 12.5 6.7": ["insulitis"], "5.8 13.9 5.6": ["immunofluorescent"], "4.8 14.7 4.7": ["cataleptic"], "3.6 -0.5 0.6": ["ayor"], "-0.6 6.1 17.7": ["narinig"], "14.1 8.5 16.7": ["anic"], "-4.1 -2.6 2.7": ["edia"], "-0.2 6.2 14.2": ["curanderismo"], "19.8 13.1 24.4": ["bettongs"], "19.4 8.4 28.7": ["madrona"], "11.7 -5.5 9.6": ["wopping"], "0.5 9.2 4.9": ["kalmadi"], "14.3 3.1 12.6": ["mudcloth"], "13.2 12.0 16.6": ["packsack"], "-2.9 13.1 8.2": ["pulong"], "-0.3 3.3 16.0": ["bridgeless"], "5.2 -3.2 4.8": ["ieri"], "14.7 12.9 15.1": ["haughtiest"], "-2.7 4.0 -1.8": ["reteplase"], "13.3 12.6 11.6": ["boehner"], "1.0 0.7 5.3": ["iehor"], "-7.6 8.7 6.8": ["understaff"], "4.1 5.2 6.4": ["nonpornographic"], "13.2 10.1 9.3": ["witho"], "4.2 12.7 16.1": ["bubbadubba"], "2.9 14.5 19.5": ["transitivity"], "0.1 2.7 7.7": ["turbinate"], "5.9 8.7 11.3": ["trimly"], "-3.5 5.4 4.9": ["ultracentrifugation"], "7.1 6.7 15.6": ["kaho"], "10.9 4.0 28.6": ["haricot"], "-0.1 20.4 -5.6": ["stren"], "2.9 10.0 7.1": ["endonasal"], "11.6 9.2 5.0": ["sergers"], "-4.4 9.2 -2.7": ["farooq"], "12.1 0.9 2.6": ["oversquare"], "4.2 2.0 -2.8": ["sthal"], "1.5 0.4 11.6": ["nakaraang"], "13.4 -8.7 6.4": ["gebruikt"], "14.5 20.6 26.2": ["celandine"], "9.5 -2.4 12.1": ["misbrand"], "-11.1 0.0 6.9": ["sysfs"], "9.1 13.8 18.7": ["lyssavirus"], "19.8 8.2 13.9": ["rechristens"], "-0.7 9.5 12.2": ["tuttis"], "1.3 -0.7 6.6": ["choisir"], "-8.0 5.6 11.1": ["generalisability"], "-0.9 1.0 11.4": ["kelsey"], "5.8 14.8 17.9": ["ubiquitins"], "8.7 23.8 9.9": ["socialistically"], "9.2 -1.4 8.0": ["domra"], "13.5 6.4 36.8": ["hashbrown"], "10.4 3.3 1.1": ["throughits"], "9.3 -0.3 1.8": ["autonome"], "2.4 11.0 17.8": ["dodgin"], "6.6 3.7 10.1": ["outaced"], "2.4 3.9 8.8": ["trousseaus"], "1.8 9.4 12.9": ["overpitches"], "13.5 14.2 8.1": ["bawler"], "20.0 3.3 24.2": ["ventana"], "1.3 6.4 16.0": ["jaf"], "9.5 9.3 22.1": ["spectabilis"], "2.6 -6.1 3.9": ["giornata"], "-4.9 2.3 -4.9": ["cyberbegging"], "16.1 13.1 29.5": ["gorgonian"], "11.4 2.8 7.0": ["stakers"], "3.2 5.6 20.0": ["depensa"], "12.6 32.0 15.4": ["diasters"], "-2.0 3.1 7.3": ["antidiarrheal"], "0.8 4.8 3.2": ["estern"], "6.2 6.0 4.7": ["kgf"], "6.9 -2.1 9.1": ["sopo"], "16.4 12.8 16.3": ["pollos"], "15.6 6.7 14.7": ["bleue"], "7.9 5.2 10.2": ["bhara"], "1.8 10.5 11.5": ["laryngospasm"], "10.1 -2.0 3.5": ["methacrylates"], "21.6 4.7 25.4": ["karri"], "7.5 9.2 23.0": ["gingerol"], "3.4 -0.2 2.8": ["equiva"], "3.0 3.8 -1.0": ["fuelings"], "3.9 6.2 5.7": ["andgeneral"], "9.9 20.2 15.3": ["overruff"], "5.7 3.9 4.3": ["nuun"], "-10.6 9.9 0.1": ["uulu"], "6.4 8.4 18.1": ["mancha"], "12.8 -2.4 36.5": ["bellota"], "11.4 -2.2 2.2": ["ficlatuzumab"], "9.0 10.2 8.1": ["grousers"], "19.4 16.1 35.3": ["overwashed"], "23.4 1.7 33.5": ["leghorn"], "1.7 14.3 15.1": ["nerving"], "25.6 15.7 19.4": ["ratcatcher"], "4.1 7.9 11.3": ["antiharassment"], "-6.7 31.8 6.0": ["assaultman"], "16.9 11.4 31.0": ["frigatebirds"], "12.4 23.9 12.2": ["beareth"], "2.3 11.1 12.9": ["archivally"], "-1.3 14.6 11.2": ["amphotericin"], "3.4 -1.1 2.1": ["optout"], "11.7 -0.4 2.7": ["followspot"], "7.0 11.7 2.8": ["unenthralled"], "13.1 20.9 2.4": ["legitimatizing"], "6.9 4.4 16.9": ["laman"], "11.2 5.9 7.4": ["migo"], "-2.3 -4.2 8.2": ["holdthefrontpage"], "9.5 -0.2 5.1": ["disponibles"], "5.1 -3.1 5.2": ["sical"], "-12.4 10.9 6.6": ["paygrades"], "4.5 5.5 6.1": ["orgullo"], "3.2 5.5 0.4": ["spielt"], "7.9 7.9 13.3": ["larcency"], "3.5 8.6 12.5": ["signif"], "-0.4 -5.2 2.6": ["rtn"], "-0.0 11.8 2.9": ["knesset"], "-2.1 7.4 3.6": ["frpm"], "5.4 22.8 17.8": ["constantine"], "9.2 6.5 1.9": ["plastomers"], "4.4 0.7 11.7": ["lator"], "11.5 13.5 22.3": ["sooky"], "3.9 6.2 5.8": ["insurors"], "8.5 3.5 24.4": ["creperies"], "6.3 -0.5 16.3": ["neige"], "4.5 2.5 9.8": ["recibir"], "14.7 15.7 15.7": ["presplit"], "12.6 7.7 16.3": ["mwa"], "6.6 13.4 -1.6": ["demisting"], "3.3 -1.3 2.2": ["athan"], "-0.4 8.0 10.1": ["rone"], "12.8 8.0 43.9": ["sublegal"], "3.8 8.2 11.3": ["misnumbered"], "9.6 11.4 16.6": ["dropp"], "7.2 1.9 27.0": ["softneck"], "18.4 4.2 37.4": ["tostado"], "0.4 7.1 5.3": ["biomedically"], "18.8 1.2 24.0": ["buttercrunch"], "15.0 13.7 28.9": ["bunchberry"], "7.0 -3.1 5.0": ["bangbus"], "0.4 3.6 -0.6": ["lert"], "8.6 8.3 29.8": ["eatings"], "4.7 13.3 17.1": ["teleconnections"], "8.7 16.2 13.6": ["comeon"], "6.5 0.1 17.9": ["pagode"], "13.0 23.8 10.1": ["extortioners"], "2.7 2.1 8.2": ["possi"], "12.6 14.1 23.5": ["slackwater"], "-2.7 5.8 9.9": ["tungkulin"], "-9.2 7.5 5.5": ["ilities"], "10.3 14.0 4.4": ["aeroelastic"], "7.4 4.8 8.2": ["siguen"], "8.5 8.6 7.2": ["dollarize"], "-0.2 7.1 18.8": ["kalsada"], "6.2 9.2 22.5": ["scandens"], "7.4 9.9 17.5": ["tumne"], "11.6 2.1 11.8": ["semplice"], "9.3 3.4 15.9": ["mirrorwork"], "11.0 0.8 0.1": ["vendre"], "14.8 0.8 16.6": ["unstyled"], "2.5 13.1 9.6": ["viri"], "11.7 9.0 8.7": ["myxoma"], "8.7 7.0 -2.0": ["nchez"], "12.4 10.5 -5.9": ["motorcading"], "8.2 -1.2 7.9": ["sommet"], "11.8 6.5 19.7": ["antennal"], "-6.5 -3.1 1.9": ["mtgs"], "-5.5 12.3 9.6": ["rakhna"], "-4.0 -1.5 -0.0": ["frederick"], "18.8 6.2 21.2": ["naugahyde"], "0.5 -2.0 6.5": ["codi"], "2.9 3.7 10.1": ["ambrotypes"], "-3.3 -2.8 13.1": ["irvine"], "2.3 15.2 17.1": ["munhu"], "8.0 3.8 0.6": ["emailable"], "9.4 5.5 7.6": ["cuore"], "9.8 11.2 6.4": ["ungroup"], "8.3 16.9 11.2": ["helicobacter"], "7.5 11.6 6.0": ["rewetting"], "15.0 2.8 16.9": ["lobata"], "13.9 0.7 3.1": ["ncludes"], "3.9 0.8 6.0": ["alexandra"], "6.8 13.0 7.5": ["egalite"], "1.9 15.9 2.6": ["individu"], "5.9 2.9 14.1": ["rada"], "8.4 -3.7 12.1": ["lorn"], "10.1 6.7 12.4": ["nanoarrays"], "2.6 3.9 6.1": ["chercher"], "13.9 11.5 28.4": ["baculum"], "5.4 5.3 6.3": ["mischarging"], "-6.9 -2.1 4.9": ["superindent"], "1.7 9.3 6.2": ["fvc"], "16.3 14.0 17.6": ["rapelled"], "11.7 0.2 16.2": ["cornell"], "5.7 1.5 20.7": ["alpina"], "17.4 3.2 2.2": ["inlicensing"], "0.3 4.2 2.3": ["nonbargaining"], "23.0 5.1 26.0": ["skimmings"], "7.8 15.7 4.2": ["symp"], "-0.6 -5.1 9.2": ["databse"], "-7.9 14.3 2.1": ["repre"], "1.5 10.3 5.9": ["samman"], "0.4 7.7 7.7": ["runspace"], "18.1 19.7 13.8": ["inhospitably"], "3.1 3.5 16.3": ["weston"], "18.6 13.7 21.4": ["twistin"], "7.1 3.2 -5.0": ["stylizes"], "3.1 1.1 13.3": ["meenakari"], "6.8 4.9 14.8": ["shtreimel"], "1.8 15.8 14.2": ["fainters"], "16.0 12.7 18.8": ["xu"], "1.5 7.2 14.2": ["testigo"], "-0.5 0.6 4.0": ["eceived"], "3.4 8.9 16.3": ["stonier"], "14.1 5.3 36.7": ["molluscan"], "16.2 1.7 13.1": ["scoopneck"], "17.8 9.1 18.7": ["mounters"], "14.3 7.2 9.1": ["dykey"], "-3.8 -6.4 6.1": ["clomifene"], "8.1 -1.2 7.1": ["eerder"], "18.5 7.1 14.2": ["phoria"], "17.5 2.3 -2.5": ["opel"], "4.4 6.8 5.7": ["hrd"], "6.2 10.1 18.9": ["backspread"], "17.2 22.2 19.9": ["blackhawk"], "11.6 2.9 25.6": ["kippered"], "15.9 -0.3 29.7": ["gemelli"], "11.9 7.5 -3.5": ["nanophosphate"], "15.2 9.2 20.6": ["bushtucker"], "10.2 8.2 11.6": ["saxon"], "17.4 17.5 8.1": ["prograde"], "13.5 15.0 11.4": ["intervallic"], "19.7 6.9 43.2": ["thermidor"], "-0.0 8.9 13.6": ["cyclogenesis"], "22.3 8.4 26.7": ["caymans"], "2.0 12.8 14.9": ["phototoxic"], "9.2 4.7 5.9": ["multicard"], "1.8 17.3 1.2": ["autothrust"], "12.4 -3.4 16.7": ["bioresource"], "11.6 6.3 -2.2": ["setzt"], "7.2 1.0 12.9": ["malondialdehyde"], "20.0 -1.3 -1.2": ["gematik"], "5.7 6.6 11.2": ["whaa"], "9.8 8.9 11.8": ["microcephalics"], "7.7 7.2 18.8": ["cornwall"], "5.8 2.4 12.9": ["felsite"], "14.6 10.5 26.5": ["casaba"], "15.0 7.9 48.3": ["akule"], "0.5 3.2 -6.9": ["ience"], "10.7 -3.8 4.5": ["presitgious"], "4.2 23.6 9.6": ["delibrately"], "2.6 -4.9 6.5": ["isobutyl"], "8.3 12.0 9.9": ["succesion"], "2.7 -4.5 6.4": ["periode"], "1.7 -5.5 17.4": ["ibanez"], "4.7 -1.9 20.0": ["chut"], "8.8 6.4 -2.6": ["ifm"], "1.6 8.2 6.7": ["laisser"], "17.9 1.8 42.9": ["cappellini"], "12.0 15.1 12.9": ["disappered"], "3.9 3.7 6.0": ["barrowed"], "-5.2 1.0 8.9": ["trailbuilding"], "6.0 4.0 10.1": ["withher"], "7.3 16.4 10.2": ["talkiness"], "1.2 2.8 13.7": ["fibrillin"], "3.8 2.7 3.9": ["biosample"], "15.1 4.9 16.0": ["klatsch"], "9.9 12.1 9.8": ["bossiest"], "15.2 20.1 12.5": ["aproaching"], "9.8 -4.8 15.4": ["easi"], "18.9 2.7 25.1": ["lapful"], "8.6 10.3 11.4": ["glebe"], "1.5 2.8 12.7": ["testerone"], "-2.5 -2.3 18.6": ["soyfood"], "6.7 16.9 12.0": ["priniciples"], "11.5 3.4 40.4": ["tetrazzini"], "1.1 11.3 5.4": ["decompensating"], "9.2 19.1 11.0": ["dicator"], "11.2 13.3 12.8": ["unrespected"], "8.9 5.9 7.3": ["declaraciones"], "18.6 15.6 24.3": ["bracer"], "1.9 -1.0 11.1": ["fleurs"], "11.0 10.3 23.8": ["cheetal"], "3.0 1.2 12.2": ["ncs"], "2.5 -4.6 5.3": ["mittee"], "10.1 10.1 10.8": ["cierto"], "4.8 15.7 14.2": ["bitwise"], "0.6 4.1 6.7": ["mammoplasty"], "10.7 14.0 11.6": ["thenews"], "7.8 -8.5 -1.0": ["lorsque"], "5.2 6.4 6.3": ["humanin"], "0.9 9.3 7.1": ["undervoted"], "12.1 4.4 23.5": ["kernals"], "11.7 17.1 14.3": ["flaccidly"], "-12.1 -1.4 5.9": ["sively"], "5.4 21.4 4.2": ["headsman"], "2.7 1.6 13.8": ["eaux"], "1.5 -2.0 5.8": ["infrapopliteal"], "6.5 6.2 24.8": ["qian"], "-0.9 8.1 1.5": ["chalisa"], "9.1 7.0 -4.0": ["goalkeeeper"], "12.4 7.9 18.5": ["ritchie"], "3.3 9.4 6.2": ["skewerings"], "13.9 26.3 15.0": ["gheraos"], "-0.3 2.1 14.4": ["gyntaf"], "-2.6 20.5 5.3": ["directable"], "13.2 9.5 11.8": ["stumblin"], "-0.3 0.5 9.5": ["shivir"], "19.2 -0.4 15.9": ["warehouser"], "10.5 -0.4 -2.7": ["istradefylline"], "12.7 13.9 12.4": ["dollarise"], "3.4 5.8 2.7": ["detai"], "6.9 -0.4 10.2": ["doubletakes"], "16.8 13.0 22.4": ["brek"], "7.1 4.3 24.9": ["geum"], "11.3 13.6 23.7": ["pademelons"], "5.2 8.9 1.5": ["jhappi"], "5.0 9.9 9.5": ["galactosidase"], "-12.5 4.4 -0.2": ["illnes"], "12.2 17.0 10.5": ["himin"], "16.8 2.3 15.0": ["fauteuil"], "14.3 5.9 19.6": ["dogo"], "-0.3 7.5 10.5": ["compos"], "6.9 -3.2 6.5": ["showpeople"], "10.0 2.6 13.0": ["carro"], "14.3 22.2 9.3": ["epicyclic"], "11.4 -0.1 16.2": ["medly"], "-11.2 -0.1 9.5": ["selec"], "1.5 9.5 2.6": ["relaxivity"], "-4.7 1.0 -2.0": ["setcom"], "11.1 5.4 16.0": ["colorblocked"], "5.5 11.2 -3.1": ["haad"], "12.8 8.8 20.0": ["hines"], "12.7 2.3 3.8": ["wallmount"], "5.0 15.4 9.9": ["fick"], "11.3 13.9 19.7": ["sailboarder"], "-0.4 7.4 10.4": ["deterioriated"], "14.0 19.1 12.5": ["disport"], "6.9 1.8 16.6": ["remy"], "32.2 18.2 10.3": ["cementer"], "-1.7 0.2 19.4": ["sudangrass"], "9.4 22.3 11.8": ["baz"], "9.9 14.3 5.6": ["extinquished"], "9.8 2.4 21.5": ["spicata"], "1.9 9.9 5.5": ["prosecutory"], "14.6 13.3 5.2": ["phreakers"], "7.8 11.3 8.5": ["pota"], "11.1 7.2 32.7": ["diavolo"], "13.9 8.2 19.3": ["beachwalk"], "-3.6 -8.6 3.4": ["catholique"], "-2.7 -8.4 5.9": ["steroidogenesis"], "18.0 19.8 16.9": ["maties"], "10.8 2.2 2.6": ["phosphorylcholine"], "13.2 6.7 16.2": ["rockered"], "0.5 9.6 12.4": ["ordo"], "9.3 21.3 21.3": ["moros"], "13.1 5.2 3.8": ["reprivatisation"], "26.7 8.4 15.5": ["spraycan"], "-2.5 4.2 -2.5": ["ompetition"], "-0.8 16.4 11.4": ["ladka"], "-0.2 14.5 13.6": ["endonucleases"], "-0.3 -2.6 12.1": ["grah"], "9.5 9.0 11.7": ["hewitt"], "5.3 15.2 1.5": ["prestate"], "5.2 7.1 15.1": ["jivey"], "5.3 5.1 11.2": ["duhs"], "6.0 3.6 9.7": ["tercera"], "3.1 7.6 13.6": ["anneals"], "16.8 15.3 8.1": ["paulson"], "-1.8 11.4 10.2": ["dictions"], "-5.7 0.4 -2.6": ["esource"], "5.2 12.2 -0.7": ["decompressor"], "5.4 1.2 11.4": ["anniversaire"], "2.8 9.1 -4.2": ["imbursement"], "3.0 2.2 13.7": ["memorie"], "13.4 3.8 8.8": ["biostructures"], "7.1 6.9 10.2": ["constante"], "15.8 1.6 8.9": ["stairclimb"], "13.2 6.4 29.0": ["meltable"], "2.3 2.4 4.0": ["voll"], "7.2 5.1 7.2": ["buzziness"], "4.9 -3.7 20.6": ["dair"], "4.3 9.3 22.3": ["perang"], "1.0 9.3 7.9": ["myometrial"], "16.2 6.9 4.2": ["grommeted"], "9.7 -2.4 19.0": ["produkto"], "8.7 23.4 11.2": ["helpside"], "10.3 15.6 20.8": ["carnivory"], "6.9 13.8 6.2": ["wordlist"], "20.6 7.5 8.9": ["severl"], "10.1 3.3 16.6": ["travers"], "4.1 13.4 14.0": ["peligro"], "13.8 -5.2 7.8": ["smartish"], "2.1 14.2 19.3": ["awon"], "10.9 6.6 17.2": ["amosite"], "25.0 10.3 30.8": ["oviraptor"], "-3.4 7.2 9.3": ["kakayahan"], "19.0 8.4 19.3": ["okc"], "-4.9 3.2 8.0": ["sweeney"], "16.2 6.9 10.5": ["bonniest"], "-1.1 6.6 3.9": ["euroisation"], "15.7 5.0 -5.5": ["zavod"], "24.3 6.4 20.6": ["cogged"], "19.2 3.7 3.5": ["jems"], "14.3 7.8 18.1": ["procees"], "11.6 5.7 6.8": ["latexes"], "6.5 -6.7 5.1": ["tinued"], "9.2 0.2 3.0": ["bharti"], "2.0 -2.0 15.5": ["binigyan"], "6.3 15.0 2.4": ["geoeffective"], "-1.9 6.9 2.4": ["ministre"], "2.4 -2.7 -6.7": ["presidentand"], "-11.0 -1.3 5.2": ["urogynecologists"], "8.4 28.3 9.0": ["standeth"], "17.8 10.7 21.9": ["mielie"], "6.0 6.5 8.6": ["eucalyptol"], "-1.9 -1.5 0.1": ["nutzen"], "2.9 3.1 7.7": ["megadump"], "21.8 2.9 47.3": ["krab"], "13.2 9.4 22.4": ["oarsome"], "-2.5 5.0 7.8": ["pheresis"], "2.1 8.8 4.1": ["clm"], "5.5 4.6 9.2": ["gtx"], "2.4 1.7 4.3": ["hyperphosphorylation"], "19.5 -0.3 20.9": ["choclo"], "4.0 8.6 13.7": ["rigueur"], "-1.1 2.1 4.9": ["manslaugher"], "0.8 10.0 11.1": ["parce"], "5.7 2.6 3.8": ["unsecuritized"], "6.8 17.9 17.8": ["bess"], "9.7 1.4 13.6": ["butylated"], "9.0 8.7 8.4": ["hydrovac"], "5.6 1.4 12.4": ["cynnal"], "-0.9 -0.0 1.4": ["hematopathologists"], "4.4 0.2 14.3": ["avanti"], "-1.2 7.9 16.7": ["kuwento"], "5.4 2.2 15.9": ["journeypersons"], "7.3 7.3 6.1": ["replicar"], "-2.6 3.7 -9.3": ["nabi"], "22.2 3.9 18.8": ["bogof"], "-3.3 10.1 13.7": ["faits"], "15.4 11.0 21.9": ["potoroos"], "12.1 2.8 17.5": ["banjoes"], "20.5 -1.2 14.4": ["bavarian"], "5.4 3.9 7.5": ["conjestion"], "1.9 16.1 12.5": ["preconscious"], "-3.8 1.9 6.5": ["baroreceptor"], "16.9 4.6 30.8": ["froglet"], "4.1 14.6 18.5": ["krumper"], "8.4 1.1 10.3": ["chylomicron"], "-3.3 4.3 5.5": ["electi"], "2.5 -3.3 19.3": ["prah"], "2.2 9.7 5.8": ["ethmoid"], "3.9 2.8 0.7": ["jetblue"], "2.8 14.0 3.0": ["seekin"], "11.7 14.5 6.6": ["hatchways"], "1.1 7.1 15.5": ["udhar"], "2.9 1.0 7.2": ["pervitine"], "8.3 22.0 8.9": ["foxhunter"], "8.8 4.8 26.8": ["pubescens"], "7.2 10.5 2.6": ["nonsexist"], "11.6 17.6 10.3": ["cerebro"], "2.4 5.6 11.9": ["hmb"], "6.3 6.5 0.7": ["atp"], "13.0 9.1 21.3": ["muggins"], "-2.6 -6.0 -0.5": ["iks"], "-6.6 7.2 -5.6": ["reconceptualizing"], "11.4 5.8 0.8": ["cronie"], "-6.1 4.8 9.4": ["cofiring"], "16.1 25.4 12.9": ["gloaters"], "14.0 -5.8 6.7": ["overy"], "13.5 0.5 10.9": ["neckbands"], "6.8 5.5 6.0": ["kaons"], "1.0 9.8 16.7": ["swansea"], "19.0 4.9 35.8": ["mozzerella"], "-15.1 10.1 -0.1": ["repsond"], "15.9 -6.3 10.0": ["nline"], "3.4 19.0 3.4": ["facepiece"], "11.2 10.9 44.2": ["garibaldi"], "12.3 2.3 28.4": ["unenriched"], "-0.0 -3.8 16.1": ["primeur"], "-0.1 -0.7 9.9": ["butorphanol"], "14.1 8.6 8.1": ["texta"], "11.1 8.0 6.7": ["developme"], "20.4 5.5 40.5": ["aquacultured"], "13.6 4.9 10.8": ["overstored"], "9.3 8.6 16.0": ["mascaraed"], "11.5 5.7 16.6": ["tsair"], "-1.5 -8.0 2.8": ["tainer"], "10.1 11.6 15.3": ["quanities"], "14.0 9.0 20.6": ["palos"], "20.6 13.0 32.2": ["fluffernutter"], "7.3 26.1 5.6": ["choiceless"], "2.3 12.1 4.1": ["degenerations"], "-3.8 -7.3 8.3": ["microsomes"], "8.7 7.2 9.3": ["cruciverbalist"], "2.2 -0.3 21.1": ["sml"], "4.5 8.4 10.5": ["longueur"], "20.0 -0.1 15.3": ["redbull"], "15.6 8.6 35.9": ["kelps"], "15.0 11.1 9.8": ["energos"], "-7.1 4.7 3.7": ["finalizations"], "13.6 -6.1 -2.6": ["maxx"], "8.4 -5.6 0.4": ["combin"], "11.2 9.0 19.2": ["hurly"], "10.7 7.2 12.7": ["subpage"], "17.7 -0.8 -4.7": ["cabsat"], "8.8 8.7 28.7": ["forno"], "0.5 6.1 7.1": ["xual"], "3.7 3.0 -2.5": ["esident"], "7.8 16.8 8.5": ["homochirality"], "-9.7 0.3 0.4": ["sday"], "3.5 14.7 7.0": ["saamne"], "2.7 6.7 3.2": ["disallowable"], "19.0 12.0 26.8": ["crewboats"], "3.7 2.6 10.5": ["cuyo"], "1.1 6.0 -2.3": ["antihypertension"], "11.3 2.5 5.7": ["entrega"], "-4.1 13.7 22.1": ["matwork"], "7.3 2.0 13.0": ["enige"], "-11.4 1.8 1.2": ["dismutase"], "8.9 2.4 0.4": ["vostro"], "17.5 3.8 10.1": ["krijgen"], "8.1 2.6 8.3": ["multinight"], "12.9 18.3 17.0": ["supereasy"], "3.5 4.6 12.5": ["olivier"], "13.0 17.7 9.1": ["marinized"], "9.9 24.9 12.0": ["preditor"], "15.1 16.8 15.0": ["badda"], "5.4 5.8 2.0": ["rold"], "7.5 15.0 22.5": ["uchi"], "8.2 -0.2 11.7": ["specula"], "6.3 -2.6 6.6": ["somatotropin"], "6.3 3.2 16.8": ["coldrolled"], "1.4 20.7 11.7": ["shekhar"], "5.7 15.0 14.1": ["westabout"], "-4.7 13.3 -5.5": ["aircraftman"], "4.6 -2.3 9.4": ["gydag"], "1.8 4.5 9.1": ["baki"], "14.3 17.0 14.1": ["virtu"], "5.3 32.0 7.5": ["breacher"], "14.3 0.0 12.9": ["rebozo"], "-7.7 11.8 7.7": ["extrabudgetary"], "5.3 11.7 10.5": ["trophoblasts"], "-2.1 5.6 1.4": ["hydrobromide"], "7.5 -3.4 9.7": ["defnyddio"], "0.4 -0.3 5.1": ["civamide"], "3.5 7.2 14.1": ["tswa"], "3.7 0.6 12.9": ["buques"], "12.1 12.8 18.3": ["superfreighter"], "7.2 4.5 11.2": ["tagout"], "4.6 -2.5 7.6": ["intracapsular"], "11.0 7.4 15.8": ["taghhom"], "16.9 -0.4 8.5": ["manufactur"], "12.6 25.4 8.9": ["valient"], "3.9 3.6 15.6": ["nagulat"], "13.0 2.6 -1.0": ["tablatures"], "13.5 12.3 29.4": ["nibbly"], "-9.3 5.3 -6.0": ["ovich"], "8.7 15.1 8.7": ["liest"], "6.3 6.9 2.9": ["oben"], "2.3 6.3 13.5": ["multielement"], "5.1 7.1 7.2": ["nanosponge"], "16.2 4.5 -4.9": ["powerd"], "9.5 3.6 15.2": ["preshrunk"], "6.7 -1.6 -0.0": ["naturelle"], "10.4 1.6 21.5": ["retox"], "-6.9 17.4 1.5": ["responsiblility"], "4.3 17.8 7.4": ["barbz"], "12.7 28.4 14.7": ["coastguardsmen"], "2.7 5.5 6.7": ["zweite"], "14.6 14.1 9.1": ["backwardly"], "12.5 12.4 28.8": ["honeycreeper"], "6.3 5.5 14.0": ["sulfoxide"], "12.7 -0.1 0.5": ["philanthrophic"], "12.4 -4.0 -2.9": ["pharmaceutique"], "-1.1 -2.5 1.5": ["thromboembolisms"], "12.8 11.0 9.8": ["blogspace"], "7.9 10.6 11.1": ["lavaliere"], "8.4 -4.9 3.1": ["tercero"], "13.7 2.7 4.5": ["chloroflourocarbons"], "7.0 9.5 25.1": ["lagered"], "8.3 8.9 3.0": ["doolies"], "2.5 8.0 7.8": ["motability"], "-14.4 8.2 1.8": ["rahim"], "-3.3 11.4 3.9": ["sagest"], "0.5 6.1 5.6": ["autunite"], "1.4 -0.9 8.4": ["objectifs"], "-0.7 6.7 11.9": ["mabuting"], "15.6 13.1 21.0": ["lutzes"], "-8.1 21.8 17.2": ["deckplate"], "10.6 0.5 5.9": ["tombe"], "11.9 8.0 26.8": ["piko"], "21.6 11.7 27.5": ["babby"], "17.8 13.0 14.4": ["claus"], "-3.0 2.5 20.6": ["malalaman"], "10.2 22.0 17.0": ["tranq"], "9.3 -1.7 7.3": ["lionel"], "4.4 6.2 -2.1": ["tacrine"], "-3.1 13.5 8.9": ["impt"], "9.2 13.3 11.7": ["skidplates"], "1.1 8.5 14.3": ["periodista"], "8.4 -1.3 -0.4": ["tauted"], "5.3 19.4 18.4": ["looooooove"], "15.5 3.9 19.4": ["texturised"], "-4.1 1.1 12.0": ["pumayag"], "11.0 0.5 13.5": ["jules"], "6.9 14.9 13.8": ["ramorum"], "9.6 15.2 13.9": ["flagstaffs"], "-0.8 5.8 9.9": ["krimen"], "2.4 7.0 18.7": ["kahe"], "22.5 41.9 10.5": ["decepticons"], "-2.8 15.3 4.1": ["yyyy"], "13.3 14.2 5.1": ["rearguing"], "15.3 5.9 9.6": ["mantener"], "7.5 6.2 14.7": ["kindie"], "21.1 18.9 4.9": ["vaingloriously"], "21.2 4.3 30.7": ["pondside"], "-1.1 -4.3 17.7": ["chis"], "12.1 -2.4 -1.6": ["biobetter"], "20.2 3.9 13.7": ["campitos"], "-1.4 28.4 5.4": ["sabr"], "0.5 -0.8 3.1": ["debido"], "5.4 5.6 10.0": ["scelerisque"], "10.8 8.5 15.4": ["warmdown"], "17.3 10.1 17.6": ["kneck"], "3.9 6.0 13.9": ["sheitel"], "2.0 15.2 -0.3": ["canalized"], "6.7 8.3 12.8": ["escala"], "25.5 -1.8 7.9": ["bankin"], "10.8 13.7 8.4": ["netbsd"], "3.0 6.6 12.4": ["nonsynonymous"], "4.7 1.6 6.1": ["bachchan"], "9.0 -1.8 1.2": ["fluentials"], "7.8 9.9 11.5": ["grunginess"], "11.9 10.4 14.9": ["mongolian"], "-0.2 1.7 18.2": ["roni"], "6.5 4.0 6.4": ["decellularized"], "5.0 11.5 10.0": ["ryeong"], "11.6 29.7 12.0": ["somene"], "3.5 23.1 -4.8": ["devastative"], "10.5 -1.5 15.1": ["goatie"], "-1.6 4.8 -1.5": ["oreign"], "8.3 4.4 10.6": ["tiss"], "22.1 17.8 21.0": ["bristlecones"], "7.2 11.6 8.2": ["rendre"], "1.1 1.4 -6.4": ["publie"], "7.9 14.6 -4.0": ["unassailed"], "4.2 5.0 9.4": ["rcent"], "2.3 7.2 11.2": ["biotitic"], "3.4 6.4 5.8": ["sugges"], "9.0 -4.5 -0.5": ["confererence"], "7.5 13.3 28.7": ["cascara"], "7.0 10.1 15.0": ["monstre"], "4.0 5.7 19.1": ["eatwell"], "7.7 2.5 8.1": ["artikel"], "12.1 6.3 21.2": ["bioinformaticists"], "-4.0 4.5 5.3": ["kyokushin"], "18.7 7.0 5.8": ["bikemaker"], "3.3 4.2 9.8": ["raksha"], "3.4 15.2 9.5": ["uninterruptable"], "4.9 11.9 -0.0": ["arer"], "3.5 0.1 1.5": ["chloroprene"], "7.3 11.3 14.8": ["vecinos"], "10.8 0.8 18.6": ["marley"], "2.1 3.8 8.9": ["intratracheal"], "-0.7 7.0 5.9": ["tallitot"], "8.1 12.5 13.6": ["heee"], "5.2 -1.1 8.2": ["precios"], "-2.8 7.6 11.6": ["oposisyon"], "5.9 0.9 7.5": ["nimmt"], "6.0 -0.1 3.6": ["featur"], "9.9 17.5 16.9": ["nieghbors"], "-4.4 16.5 2.3": ["swearers"], "14.0 6.6 13.2": ["manhoods"], "-7.8 -1.5 4.1": ["spea"], "0.9 -0.9 3.7": ["advi"], "13.6 17.1 23.8": ["budda"], "9.3 -0.9 6.7": ["horserider"], "19.9 8.9 18.6": ["skidsteer"], "3.0 9.0 13.7": ["bioaerosol"], "4.3 17.5 9.9": ["monoculturalism"], "-6.0 3.8 7.5": ["thorne"], "-5.5 10.8 1.4": ["ferumoxtran"], "6.3 5.1 1.0": ["dihydro"], "-2.8 5.2 9.1": ["natriuresis"], "-2.3 -0.1 10.1": ["tajjeb"], "12.1 -2.1 23.4": ["dangos"], "11.9 2.7 9.8": ["obras"], "4.0 10.8 3.0": ["nitrosothiols"], "18.0 11.8 27.1": ["trapezing"], "-0.5 14.8 12.6": ["oligodendrogliomas"], "20.0 14.6 20.7": ["mopane"], "-2.9 3.4 6.4": ["tetrahydrobiopterin"], "15.5 6.9 16.8": ["gumby"], "11.2 5.5 11.2": ["mium"], "6.1 5.0 15.2": ["profundo"], "0.3 0.9 3.7": ["iiii"], "-0.2 1.6 5.5": ["cano"], "-1.5 -0.5 2.8": ["electrodeionization"], "-3.9 24.6 1.3": ["tanzeems"], "8.9 14.9 7.3": ["provirus"], "-4.0 10.7 -0.6": ["accordign"], "10.9 0.8 12.6": ["inseminator"], "10.5 16.8 7.3": ["reburies"], "9.2 17.1 18.4": ["intraplate"], "9.3 14.0 18.5": ["champa"], "9.2 5.7 15.9": ["clappy"], "4.8 8.0 11.6": ["reaso"], "3.2 6.9 16.5": ["exotherm"], "0.5 11.2 15.7": ["amra"], "2.9 4.7 11.2": ["anony"], "5.9 4.0 5.5": ["advan"], "16.3 4.3 14.6": ["ingresos"], "8.6 -2.2 9.7": ["potentiel"], "5.7 -5.4 5.0": ["struc"], "-1.3 -4.1 13.6": ["transmix"], "9.7 4.9 10.6": ["dosimetrists"], "13.3 19.7 1.2": ["cyberczar"], "21.0 13.2 20.9": ["meerschaum"], "0.4 -0.5 13.9": ["noncalcified"], "2.9 3.5 3.2": ["eknow"], "15.7 8.8 24.4": ["puffa"], "2.9 6.6 6.5": ["comenzar"], "-1.4 0.9 10.6": ["noncancelable"], "17.7 7.1 31.6": ["arbol"], "1.5 15.5 8.7": ["fusogen"], "24.1 13.1 12.8": ["gismo"], "-0.4 3.0 9.6": ["nombreux"], "8.2 -3.0 4.4": ["informatiques"], "3.5 -4.0 -5.0": ["projectjobs"], "7.5 9.6 3.3": ["uncopyrighted"], "2.4 3.7 10.4": ["conocido"], "7.2 4.7 7.0": ["vicarages"], "0.6 9.0 13.3": ["pasteurella"], "1.0 2.6 11.5": ["mutualized"], "-2.0 14.0 12.6": ["bullrushed"], "2.6 16.8 -5.9": ["adamently"], "9.1 5.2 11.0": ["hilux"], "6.3 7.0 3.2": ["perations"], "4.7 7.1 3.5": ["laboris"], "2.5 4.6 3.2": ["incor"], "-6.3 -1.6 -5.4": ["cnhi"], "11.8 10.8 11.4": ["mobbers"], "2.0 -3.4 4.8": ["suspenion"], "11.8 -4.4 9.6": ["isis"], "1.6 7.7 17.9": ["siphonage"], "-1.6 8.1 7.0": ["preven"], "5.0 23.3 9.1": ["verbing"], "18.2 7.5 4.1": ["investmen"], "9.1 7.4 9.3": ["pinksheet"], "19.6 12.0 14.6": ["makuti"], "13.1 5.4 18.7": ["bushiest"], "14.7 9.1 8.7": ["wda"], "0.7 1.5 -1.3": ["osed"], "4.4 8.1 0.4": ["reinspired"], "9.1 15.4 21.7": ["fothergilla"], "-10.1 -5.6 0.3": ["ciency"], "15.7 12.5 17.3": ["carbone"], "12.5 5.0 12.1": ["subcity"], "9.1 10.5 18.8": ["aniston"], "5.0 4.9 -0.4": ["inals"], "19.7 17.2 33.4": ["caracara"], "6.4 3.7 9.5": ["concorde"], "11.9 3.6 11.0": ["actuel"], "11.0 1.0 9.9": ["volgende"], "4.9 -4.6 7.6": ["expan"], "2.6 0.3 5.8": ["lipglass"], "0.4 0.5 -1.4": ["dihydropyridine"], "-0.1 8.0 -5.4": ["thesupport"], "12.2 11.7 11.5": ["argentinian"], "7.0 0.7 -2.3": ["publico"], "5.0 18.5 7.6": ["seethingly"], "5.8 9.3 23.2": ["manson"], "14.7 10.0 15.5": ["anaglyphic"], "8.8 1.4 6.9": ["generales"], "17.2 10.2 25.2": ["choko"], "8.8 5.8 19.7": ["morpholinos"], "13.9 2.0 20.0": ["drystone"], "8.1 9.1 31.8": ["doenjang"], "21.9 17.5 17.1": ["chisled"], "1.8 -0.6 5.7": ["erable"], "2.3 4.9 9.4": ["streamyx"], "11.6 16.8 15.2": ["warsaw"], "10.1 14.6 21.5": ["knapped"], "3.8 4.2 2.6": ["impedence"], "-1.0 1.6 5.9": ["satish"], "12.6 11.2 14.8": ["nocebo"], "1.9 13.5 9.3": ["railbelt"], "3.5 5.0 11.8": ["respecto"], "-2.8 0.5 0.7": ["edaravone"], "4.3 -8.2 2.7": ["careline"], "16.0 0.2 20.7": ["freestall"], "-0.3 9.7 -7.0": ["cryptanalyst"], "19.9 22.5 11.0": ["ejectable"], "18.7 18.8 14.1": ["geometer"], "22.8 16.8 19.4": ["hampster"], "-3.0 6.7 10.3": ["arious"], "17.6 9.7 23.3": ["manchurian"], "0.6 4.6 15.7": ["katz"], "14.8 11.6 12.0": ["moiling"], "4.9 2.8 4.4": ["broadcom"], "-0.3 0.6 7.8": ["andmaintenance"], "16.5 32.3 16.2": ["kombat"], "7.2 -5.4 10.5": ["broh"], "1.5 12.9 38.9": ["cuon"], "0.7 3.4 1.0": ["dadra"], "13.0 7.9 4.5": ["anet"], "21.0 -1.1 19.5": ["stainer"], "19.6 18.6 30.0": ["aralia"], "5.3 7.7 6.0": ["fingerscans"], "8.3 7.9 15.8": ["siao"], "-3.2 6.0 11.7": ["nanoflow"], "8.8 6.1 2.3": ["subcriber"], "5.6 5.6 14.6": ["controlee"], "8.8 13.4 15.8": ["subhorizontal"], "11.9 11.3 3.9": ["chairless"], "2.3 -1.8 25.7": ["anza"], "1.0 5.4 -3.8": ["majeure"], "-3.5 -1.2 6.9": ["mellitus"], "14.4 9.0 19.8": ["gloriosa"], "0.8 4.8 11.9": ["jaghmel"], "9.8 16.5 10.9": ["antiquark"], "0.3 7.3 18.3": ["ibigay"], "10.0 -4.1 0.8": ["sleepaway"], "-2.5 5.6 8.0": ["oko"], "15.3 11.2 31.3": ["shortcrust"], "9.0 -0.1 38.1": ["dilis"], "-4.5 13.7 11.1": ["bahala"], "-5.8 -4.5 -5.3": ["coeditors"], "7.2 27.1 20.0": ["backand"], "5.9 1.2 7.7": ["hanes"], "7.8 10.0 1.8": ["updat"], "13.8 18.9 7.4": ["overmatches"], "7.0 11.6 9.2": ["looksie"], "20.8 12.1 15.5": ["pullyu"], "3.0 18.2 10.2": ["bezerk"], "16.8 9.2 7.0": ["opended"], "5.4 6.1 2.3": ["amperometric"], "2.4 14.0 7.9": ["mangalore"], "11.9 6.2 1.7": ["sgi"], "-2.9 8.9 10.0": ["congential"], "14.6 4.7 15.1": ["grecian"], "3.7 15.0 4.7": ["accessorization"], "8.0 4.8 4.9": ["strategiest"], "12.7 12.4 11.7": ["holodecks"], "-2.1 5.0 7.3": ["thecentral"], "5.7 12.0 15.6": ["imus"], "14.1 10.4 33.1": ["squatt"], "11.7 25.4 6.2": ["janjawid"], "8.9 20.1 19.4": ["saul"], "-1.6 2.8 3.6": ["pertusis"], "1.0 15.2 4.8": ["mantrums"], "6.7 7.7 13.8": ["corriente"], "17.6 16.0 29.4": ["ferox"], "-13.5 -0.5 -0.8": ["traumatologist"], "14.8 8.8 2.1": ["publicado"], "23.0 13.9 19.8": ["goulish"], "14.4 6.7 20.5": ["ryotei"], "5.0 6.0 12.0": ["manot"], "6.2 1.3 16.1": ["desination"], "14.3 6.3 4.4": ["nontravel"], "17.1 6.4 21.0": ["geous"], "2.3 16.9 12.2": ["oryzae"], "15.3 1.0 6.5": ["digestor"], "8.2 15.6 10.6": ["diculous"], "0.4 6.8 9.5": ["thiosulfate"], "2.3 5.2 3.5": ["amyloidogenic"], "13.2 2.4 15.1": ["microwell"], "5.8 10.4 17.4": ["remineralize"], "6.6 9.7 1.0": ["xmpp"], "5.5 4.5 21.4": ["tenei"], "16.2 -0.5 5.9": ["principali"], "12.2 17.3 12.6": ["heartattack"], "12.7 -4.2 6.5": ["rivate"], "13.0 9.4 17.3": ["changings"], "7.5 11.9 14.7": ["ligula"], "5.2 3.3 7.1": ["orward"], "7.2 7.8 11.5": ["griha"], "14.1 6.0 11.4": ["ponyhawk"], "2.2 9.9 13.3": ["baith"], "9.9 18.2 11.0": ["punctum"], "-3.9 12.7 12.9": ["peritumoral"], "1.8 -2.0 13.1": ["patiala"], "1.8 -3.7 -9.0": ["currentl"], "4.0 -1.3 16.1": ["sawl"], "6.3 20.8 10.8": ["unpolarized"], "6.7 15.7 13.9": ["manush"], "3.2 5.1 7.4": ["uda"], "16.1 19.8 18.7": ["wingsuits"], "-1.7 0.3 7.7": ["precharge"], "2.7 7.3 3.5": ["syntaxin"], "-15.8 8.7 8.8": ["neutropaenia"], "13.4 1.3 12.6": ["scratchoff"], "3.7 9.3 8.5": ["pentoxide"], "16.3 8.6 1.7": ["ecko"], "1.3 8.2 10.3": ["uman"], "-5.3 20.7 3.5": ["guarantorship"], "17.4 10.2 20.8": ["gulmohar"], "2.1 8.3 7.2": ["miminum"], "11.5 3.1 21.3": ["preseasoned"], "-1.8 3.4 -4.8": ["decis"], "5.4 2.4 16.4": ["rup"], "-1.3 4.2 -6.7": ["explus"], "7.4 6.6 9.2": ["dioxygenase"], "-7.1 -2.0 -1.7": ["difluprednate"], "-0.8 -0.9 13.5": ["aelodau"], "2.8 6.6 4.9": ["daha"], "3.2 11.0 2.0": ["selfimposed"], "-0.6 -4.3 4.7": ["myhome"], "6.2 -5.8 14.2": ["yueh"], "2.5 18.8 13.5": ["overvoted"], "0.6 -8.8 2.0": ["cma"], "4.1 14.6 2.1": ["blueray"], "-5.0 14.8 5.6": ["confessedly"], "1.5 9.2 16.5": ["papasok"], "1.8 4.5 3.0": ["paraspinal"], "13.8 14.5 9.6": ["coriolis"], "-1.1 2.5 4.7": ["involv"], "13.5 14.3 19.7": ["creviced"], "6.1 5.2 5.2": ["beamz"], "6.2 13.8 4.7": ["strenthened"], "10.4 -1.1 4.5": ["electrodeposited"], "-1.8 -3.9 4.8": ["spee"], "-0.2 12.8 14.8": ["fingerpick"], "4.7 2.9 9.9": ["communidade"], "11.7 9.4 16.5": ["hypoid"], "1.4 1.5 16.5": ["menaquinones"], "14.5 -1.4 22.0": ["pourri"], "4.6 22.1 17.0": ["smily"], "7.8 9.1 13.3": ["regasifying"], "21.1 11.4 10.6": ["flugtag"], "10.0 12.9 22.1": ["manpowered"], "1.6 2.9 2.5": ["mome"], "2.8 3.5 12.0": ["uomo"], "-0.8 10.5 6.6": ["interstaters"], "4.6 9.3 7.5": ["vaccinologist"], "1.8 3.2 14.0": ["mbe"], "-0.6 5.1 6.7": ["prostanoid"], "4.0 8.9 10.9": ["keflex"], "-1.1 10.2 19.0": ["ebidensiya"], "-0.9 10.3 2.2": ["fundholding"], "4.6 14.7 18.0": ["criminy"], "-3.6 -1.3 4.3": ["lence"], "4.6 13.1 18.7": ["chokings"], "1.0 24.5 12.5": ["circumstanced"], "6.8 -11.1 22.7": ["vealer"], "-3.0 -6.0 5.7": ["prelicensure"], "12.1 15.0 13.6": ["bodywide"], "8.9 -10.1 -1.8": ["pty"], "6.4 7.9 7.2": ["rhinopneumonitis"], "-3.9 4.2 6.3": ["antiresorptive"], "4.9 11.6 27.9": ["kathi"], "7.4 1.3 12.9": ["mangala"], "11.0 -1.3 1.5": ["degludec"], "6.7 11.0 16.9": ["peroxisome"], "1.5 6.9 3.4": ["superheterodyne"], "2.9 -3.8 11.0": ["dosis"], "5.4 -4.2 20.6": ["yukon"], "6.6 6.4 33.2": ["khanom"], "6.8 0.9 2.5": ["estudios"], "12.2 5.8 14.1": ["dundee"], "11.4 2.0 5.1": ["photochromatic"], "14.7 3.8 18.7": ["siberian"], "-2.6 0.3 7.6": ["reduc"], "0.0 18.1 4.3": ["sifarish"], "11.7 4.8 8.8": ["janes"], "-5.8 0.6 1.5": ["setoffs"], "21.2 12.0 14.5": ["serrefine"], "2.4 -4.1 5.2": ["participa"], "2.5 16.7 16.5": ["waza"], "2.7 24.1 7.8": ["blurr"], "1.5 4.2 2.6": ["terribles"], "9.3 6.6 14.7": ["muir"], "3.3 4.4 11.8": ["speedweeks"], "7.0 6.0 5.2": ["fichier"], "6.4 25.7 5.6": ["dominionism"], "7.7 2.7 8.4": ["slotless"], "1.6 -2.9 2.8": ["professeur"], "17.5 -1.3 32.6": ["etouffe"], "2.0 8.9 15.7": ["sota"], "3.4 0.1 12.0": ["reticulocyte"], "-5.1 16.9 -1.6": ["nonbailable"], "17.1 14.7 9.2": ["superfriends"], "11.6 4.2 20.4": ["moxa"], "2.5 -4.8 -9.8": ["aktuell"], "6.0 -2.8 11.1": ["economica"], "10.4 22.0 20.3": ["roarer"], "10.9 5.8 12.7": ["implica"], "3.6 8.2 11.6": ["arcu"], "-2.6 10.9 2.3": ["confid"], "13.4 21.7 2.7": ["masacre"], "15.1 2.2 27.2": ["hispanica"], "6.7 4.4 1.6": ["figurers"], "9.7 -1.4 7.7": ["stora"], "5.3 3.0 12.0": ["secteurs"], "15.2 13.2 15.2": ["phyllosilicate"], "14.1 2.2 9.5": ["wacom"], "1.1 7.5 27.2": ["massala"], "-4.5 6.6 -0.3": ["isoprostanes"], "5.2 11.3 11.6": ["procrustean"], "1.9 5.7 9.7": ["goest"], "3.4 1.6 7.9": ["kumanta"], "7.7 10.4 25.7": ["bluegrasses"], "16.6 11.8 20.9": ["thwock"], "7.1 8.8 12.5": ["qabel"], "13.0 8.4 13.4": ["buscar"], "16.7 -0.3 10.9": ["markus"], "21.4 7.6 35.6": ["poboys"], "-2.1 5.1 5.7": ["dgdiscover"], "14.4 16.1 15.4": ["pistolero"], "5.3 2.3 18.3": ["informatica"], "1.2 -1.4 11.5": ["isozymes"], "-0.5 12.4 -0.6": ["economique"], "10.5 -0.3 7.0": ["apm"], "4.7 3.9 7.1": ["czechdaytrader"], "8.9 3.9 3.9": ["aleve"], "0.2 5.3 4.7": ["normoxic"], "6.5 18.7 3.5": ["militarywide"], "-0.7 -3.4 0.8": ["mayco"], "3.3 5.8 19.5": ["sportsmans"], "0.9 9.5 14.7": ["lacus"], "1.4 7.3 13.7": ["hispanos"], "4.7 5.2 6.1": ["curbless"], "2.5 9.1 2.8": ["radiometrically"], "9.5 1.8 12.7": ["candidatos"], "6.5 6.6 8.9": ["oxidases"], "7.4 6.7 8.5": ["feugiat"], "2.2 9.4 10.0": ["stockworked"], "18.2 16.4 29.9": ["stinkhorn"], "0.6 2.7 4.6": ["availments"], "16.9 -1.8 4.8": ["polyvinylchloride"], "12.3 13.8 2.6": ["addlepated"], "-0.8 -3.2 10.9": ["kontrata"], "-3.5 -0.8 9.1": ["cafodd"], "1.3 6.1 11.4": ["interconversion"], "18.5 14.5 28.6": ["palps"], "6.0 -0.3 15.6": ["keeler"], "-7.3 3.9 5.5": ["bagrut"], "3.2 4.6 18.8": ["kapalit"], "3.9 9.8 3.9": ["refore"], "14.4 10.6 23.1": ["tectum"], "12.6 20.4 13.6": ["gamester"], "15.0 7.0 17.4": ["equus"], "0.7 11.5 14.8": ["hustisya"], "6.1 11.5 11.7": ["tonalitic"], "5.6 10.6 29.8": ["paperwhite"], "0.9 5.9 4.0": ["heterojunctions"], "5.7 7.4 8.3": ["delantero"], "4.9 13.3 14.9": ["epistatic"], "12.7 1.7 13.5": ["degummed"], "14.2 17.4 15.4": ["anastomosing"], "7.2 18.2 1.1": ["migth"], "7.9 2.5 27.4": ["nicola"], "-1.6 6.0 4.6": ["yuga"], "13.5 2.6 7.2": ["brum"], "5.5 7.0 16.1": ["scaliness"], "2.6 2.1 0.4": ["otologic"], "-1.4 8.6 8.7": ["ypp"], "3.2 0.5 1.7": ["partment"], "-7.9 9.6 3.8": ["sandeep"], "4.7 1.5 13.6": ["mahvelous"], "7.6 7.3 5.6": ["emetics"], "3.1 -0.4 7.5": ["dormir"], "10.3 8.5 1.3": ["admixing"], "-2.6 8.3 9.6": ["aminopeptidase"], "5.0 -0.4 4.0": ["alth"], "-7.7 3.9 -0.9": ["clubfitters"], "14.8 18.3 9.0": ["stableboy"], "2.3 13.6 10.9": ["aprender"], "18.6 17.7 -2.1": ["handly"], "17.4 21.1 8.9": ["cybernetically"], "2.4 1.6 4.9": ["stakeswinning"], "-0.0 3.2 5.4": ["vipps"], "21.6 -1.4 18.5": ["travaganza"], "7.8 9.8 19.3": ["gagster"], "7.1 9.4 17.0": ["farrell"], "-2.3 3.4 5.3": ["rently"], "1.4 10.9 7.0": ["proteobacteria"], "0.3 2.0 14.1": ["hiver"], "-2.1 20.5 -1.7": ["sadr"], "5.5 -8.0 2.9": ["insti"], "-1.0 10.8 1.9": ["nonliterate"], "-0.9 13.5 -1.9": ["koranic"], "0.7 27.9 -2.4": ["uparmored"], "9.6 6.8 32.7": ["redbone"], "8.5 13.2 36.6": ["stewlike"], "7.1 6.5 23.4": ["dinhi"], "5.6 13.1 16.2": ["avosentan"], "10.0 10.4 5.9": ["precrash"], "-3.5 4.7 -3.4": ["commital"], "-5.3 -3.3 6.9": ["bonnes"], "12.2 9.3 12.6": ["fascin"], "3.0 12.5 2.7": ["relig"], "3.0 4.4 8.0": ["sarva"], "-1.0 13.8 5.8": ["infielding"], "1.6 8.5 1.9": ["givemefootball"], "-0.4 3.9 12.8": ["nese"], "2.8 -1.0 8.7": ["ministocks"], "-1.5 9.9 -6.2": ["stant"], "6.4 3.7 6.9": ["digitales"], "5.2 15.6 7.8": ["federale"], "4.0 7.5 7.5": ["tempdb"], "3.9 5.9 18.0": ["loe"], "16.0 6.9 13.2": ["unlaundered"], "8.2 12.9 4.9": ["organophosphorus"], "11.5 7.7 15.2": ["womanless"], "3.5 -0.3 15.5": ["laminitic"], "15.9 8.9 27.5": ["tussie"], "-2.6 -2.0 0.5": ["collaterized"], "5.7 -0.9 17.6": ["anodd"], "5.4 19.3 9.8": ["nogo"], "14.6 9.9 37.6": ["adzuki"], "2.5 0.8 8.5": ["latissimus"], "-8.2 6.4 5.2": ["trate"], "-0.8 0.5 30.7": ["melanzane"], "8.6 7.0 8.0": ["rennin"], "-2.0 3.1 11.3": ["hinahanap"], "6.7 -1.6 10.8": ["deseo"], "-2.2 6.7 10.2": ["accepte"], "8.6 12.5 26.4": ["tangan"], "9.2 4.3 22.3": ["drey"], "15.4 4.6 26.6": ["reedbuck"], "9.4 9.0 15.7": ["dion"], "6.3 13.9 16.1": ["principio"], "5.0 -3.5 6.9": ["weightman"], "11.4 17.6 7.7": ["cartographically"], "5.4 2.2 17.3": ["barrenwort"], "0.6 7.5 9.0": ["enantiomeric"], "3.1 -1.1 11.8": ["joue"], "8.6 -0.9 10.9": ["nichols"], "11.5 7.4 14.3": ["stepside"], "7.0 7.6 1.7": ["annniversary"], "7.0 1.6 14.4": ["wur"], "2.3 20.4 3.4": ["defier"], "9.6 7.4 7.6": ["methanogenic"], "19.4 5.0 16.6": ["candlewick"], "2.8 -0.4 5.7": ["ministra"], "13.4 -3.9 7.2": ["roducts"], "10.2 9.5 4.3": ["dewars"], "7.3 14.8 14.0": ["gozaimasu"], "2.0 5.6 6.2": ["derecha"], "3.3 12.1 2.3": ["lockpicker"], "6.4 4.9 12.6": ["coverslip"], "12.9 -0.5 11.5": ["tecchannel"], "-0.6 6.4 2.2": ["appendiceal"], "16.1 1.7 2.4": ["stabiles"], "-0.5 1.8 -4.2": ["basierten"], "0.2 5.0 12.3": ["kathryn"], "-1.1 2.0 4.6": ["midrasha"], "-5.9 6.2 5.4": ["inju"], "10.4 6.1 19.9": ["trinitrotoluene"], "7.3 25.5 6.1": ["malicous"], "3.2 0.6 11.8": ["jrw"], "9.8 -0.7 9.5": ["aspectos"], "-0.1 0.5 7.7": ["reinnervation"], "5.0 4.2 6.3": ["buscando"], "-4.9 -0.1 1.6": ["sehn"], "6.3 2.5 -0.8": ["highstepping"], "15.8 2.1 11.2": ["icelandic"], "5.6 12.4 17.0": ["grassweed"], "7.2 4.8 8.6": ["farmowners"], "2.1 0.3 0.3": ["coldblack"], "9.9 -3.4 11.8": ["applicazioni"], "-3.3 12.6 3.7": ["debilitative"], "7.6 6.5 14.1": ["cabine"], "17.1 -1.4 2.2": ["andconsumer"], "8.8 5.5 11.0": ["herniating"], "-3.5 2.4 10.3": ["agropastoral"], "-4.1 9.7 9.2": ["mushkil"], "20.3 14.2 19.7": ["uncompacted"], "7.7 23.8 9.7": ["miscalibration"], "-2.4 17.5 9.6": ["shortstick"], "13.2 15.2 12.1": ["skelter"], "6.4 20.0 21.7": ["licky"], "4.4 -2.8 0.6": ["developm"], "14.9 15.9 16.5": ["mudline"], "-1.7 12.4 9.8": ["nayak"], "22.8 13.4 23.8": ["ornithopod"], "-0.4 12.0 10.5": ["multiorgan"], "4.4 7.2 3.0": ["intermural"], "6.3 9.4 7.4": ["disclocated"], "4.5 19.8 5.6": ["wthe"], "8.2 15.8 10.0": ["intracluster"], "8.2 8.2 16.8": ["ocity"], "3.1 1.0 4.1": ["piloto"], "-1.1 2.1 7.6": ["adeilad"], "2.8 -1.5 12.4": ["gwybodaeth"], "9.2 4.7 1.6": ["arce"], "3.9 21.1 14.7": ["moper"], "8.7 10.3 10.2": ["noctilucent"], "4.5 -2.3 15.7": ["ferch"], "19.3 1.8 4.7": ["gfu"], "5.2 2.0 10.7": ["reforma"], "8.7 17.2 2.5": ["noising"], "-6.0 4.5 0.7": ["fatigability"], "8.6 5.9 24.8": ["boatowners"], "4.8 0.4 5.6": ["laquelle"], "8.2 11.1 16.0": ["kaufman"], "12.1 4.3 31.4": ["ginny"], "12.1 9.2 1.3": ["dowloading"], "-8.5 9.6 7.2": ["sevak"], "7.1 9.3 10.4": ["weten"], "8.1 9.6 14.0": ["tsi"], "12.8 28.2 15.1": ["pyrokinetic"], "10.2 4.8 5.0": ["hypabyssal"], "-2.3 11.6 1.7": ["currect"], "2.6 9.1 0.4": ["megaseller"], "8.0 8.2 19.3": ["taplin"], "-2.6 16.3 -5.9": ["dialy"], "25.2 11.5 38.3": ["riblet"], "9.0 15.0 7.0": ["switchmen"], "-2.5 9.7 -5.0": ["protoge"], "11.7 12.8 12.2": ["mytouch"], "13.7 4.6 3.4": ["inspiron"], "20.8 6.7 11.3": ["overexpanding"], "-5.1 3.4 4.7": ["gence"], "8.7 8.5 4.0": ["windowbags"], "14.7 3.4 8.5": ["repeatered"], "8.2 4.6 15.3": ["ulti"], "0.3 2.8 6.6": ["theplayers"], "4.6 5.7 7.8": ["jeena"], "-2.2 9.0 10.6": ["puerperal"], "6.1 1.7 7.3": ["bour"], "7.2 4.9 18.6": ["menores"], "4.3 1.8 3.4": ["dbus"], "12.4 7.2 21.6": ["tomentosa"], "-0.2 5.4 13.5": ["tumulong"], "2.8 10.8 10.3": ["secreto"], "10.6 22.4 4.6": ["cyberoperations"], "1.6 6.8 20.9": ["reoviruses"], "5.0 6.6 19.7": ["kinsa"], "19.9 3.7 39.8": ["hookbaits"], "10.6 4.3 34.9": ["goong"], "-3.0 0.8 -5.3": ["topbonus"], "15.5 11.3 25.2": ["cajeput"], "7.8 -4.0 14.6": ["muu"], "7.5 11.3 13.8": ["arenite"], "20.9 8.8 28.9": ["smushy"], "-0.5 19.4 3.0": ["dejure"], "3.5 -9.0 1.5": ["nomina"], "0.5 17.2 4.2": ["globeandmail"], "0.5 24.1 5.5": ["bismillah"], "1.7 4.5 6.8": ["galactomannan"], "19.0 7.6 25.7": ["smithii"], "4.9 3.9 12.2": ["wspm"], "20.6 11.8 26.0": ["banoffee"], "9.0 11.5 16.0": ["puno"], "11.2 11.9 2.4": ["selectorized"], "-0.8 4.8 7.0": ["unrepeatered"], "10.9 -4.1 40.8": ["keta"], "6.8 6.3 13.4": ["twh"], "0.2 7.1 3.2": ["chaupals"], "9.8 7.1 12.5": ["whichcould"], "19.9 -1.7 5.4": ["millionsof"], "13.4 10.1 -1.9": ["hinaus"], "10.5 -1.8 8.8": ["sixgame"], "24.0 2.6 2.7": ["unipole"], "14.2 16.7 11.1": ["limbos"], "-1.6 13.8 5.3": ["haemolytic"], "-1.4 6.0 12.4": ["mototaxi"], "2.3 7.7 15.1": ["tierce"], "18.7 9.4 34.5": ["phalarope"], "-0.3 5.3 -1.4": ["urg"], "2.3 5.1 15.0": ["dacites"], "10.0 -4.7 5.4": ["mgy"], "6.8 5.3 19.2": ["onetwo"], "12.5 -3.8 -5.7": ["locat"], "-2.4 2.6 8.4": ["ryun"], "16.0 10.8 11.8": ["tridimensional"], "11.3 21.7 15.4": ["bundu"], "4.2 -4.6 1.4": ["websiteat"], "13.2 22.0 21.9": ["sabering"], "2.6 -5.3 15.4": ["sylw"], "11.1 -1.6 -2.5": ["andel"], "-2.1 4.7 5.1": ["postconcussion"], "6.2 3.9 11.4": ["postemployment"], "11.3 -1.0 17.2": ["wallers"], "-0.2 9.2 8.2": ["iddle"], "2.6 9.2 7.3": ["kriged"], "19.1 1.3 18.7": ["splosion"], "8.1 11.5 2.7": ["batterie"], "11.8 10.1 22.3": ["cordata"], "12.8 5.9 10.9": ["gartered"], "0.5 24.5 6.1": ["pietists"], "1.1 -4.8 8.0": ["pagemaker"], "-2.3 -3.2 -4.3": ["participat"], "11.1 5.2 2.8": ["estadio"], "-11.7 1.2 15.7": ["malayo"], "-3.5 3.9 3.0": ["badnaam"], "17.3 1.7 45.8": ["backfin"], "-2.9 13.6 5.3": ["pind"], "10.7 12.4 12.8": ["questlove"], "10.9 4.1 10.1": ["mantapa"], "5.6 7.3 5.8": ["linus"], "6.0 13.1 8.2": ["securi"], "11.1 5.7 4.8": ["flossin"], "8.0 7.5 15.9": ["audax"], "5.3 7.2 10.0": ["krisis"], "-0.7 -1.6 10.1": ["histologist"], "18.2 0.1 7.6": ["steelcord"], "-0.5 2.3 8.2": ["facie"], "-1.3 -3.1 -2.2": ["injectants"], "16.6 9.2 2.9": ["thermionic"], "-4.7 6.8 -0.2": ["mycophenolate"], "5.8 4.9 -1.3": ["saffronising"], "2.3 5.3 13.9": ["flatpick"], "3.7 2.5 15.7": ["ystyried"], "9.2 6.3 24.6": ["bromegrass"], "3.5 5.2 8.7": ["teamming"], "8.5 8.0 7.2": ["kirstiealley"], "9.0 10.9 9.4": ["dailystar"], "8.3 10.5 33.4": ["siu"], "6.0 4.2 3.0": ["neun"], "17.8 19.8 17.3": ["thelong"], "6.4 5.6 18.8": ["balle"], "17.4 3.5 12.4": ["watercolored"], "12.5 1.3 3.0": ["verkoop"], "-2.0 29.5 7.0": ["unreachably"], "11.2 10.5 17.3": ["photoframe"], "20.1 3.2 17.6": ["stonewash"], "12.8 13.3 22.1": ["corydalis"], "14.5 16.8 19.2": ["thunderstick"], "15.8 6.0 0.9": ["superregional"], "17.5 16.1 17.7": ["warmblooded"], "10.9 2.6 8.6": ["quindi"], "19.6 8.3 6.6": ["punningly"], "-8.9 0.5 -0.8": ["overbore"], "9.8 4.9 12.1": ["angelus"], "10.7 -2.7 9.8": ["estmated"], "8.0 17.3 14.0": ["farnesyl"], "-1.7 0.0 -0.2": ["edotreotide"], "-0.2 -2.3 6.8": ["preeclamptic"], "9.8 -3.3 -1.7": ["sitelet"], "2.6 3.6 6.1": ["excelente"], "12.3 8.7 19.3": ["kyk"], "2.7 8.1 15.7": ["mismong"], "6.1 -2.7 14.6": ["wnaeth"], "10.3 11.3 3.6": ["gekommen"], "11.6 6.6 15.0": ["profesionales"], "3.3 7.6 11.5": ["osteitis"], "10.9 9.1 21.3": ["agoutis"], "14.4 4.1 8.1": ["abiogenic"], "19.8 0.1 21.7": ["roundy"], "7.6 7.3 14.1": ["refiring"], "13.3 6.3 9.9": ["nme"], "0.9 -10.8 16.8": ["kwee"], "4.3 8.8 18.1": ["necrotising"], "19.1 -0.7 7.1": ["datacommunications"], "-1.2 10.6 5.4": ["daytrade"], "17.9 11.7 22.6": ["puffleg"], "2.7 3.8 7.3": ["maydis"], "8.6 16.5 2.0": ["unslaked"], "17.9 13.5 17.0": ["reale"], "2.0 10.0 5.6": ["perineural"], "-4.2 3.3 5.8": ["nonowner"], "8.5 27.0 8.3": ["simplifiers"], "0.7 13.5 10.1": ["histatin"], "7.9 9.0 12.4": ["wann"], "5.4 8.9 6.4": ["lifeflight"], "0.0 11.6 -3.1": ["nvi"], "15.5 7.1 15.1": ["jerker"], "16.4 13.1 3.2": ["connectomics"], "13.1 6.2 12.5": ["outhern"], "7.0 8.9 15.0": ["pigmentations"], "8.9 2.3 4.9": ["myringotomy"], "4.2 13.1 10.6": ["apil"], "3.7 17.1 8.3": ["vaya"], "7.0 0.2 11.7": ["vaut"], "7.7 -3.3 6.0": ["comprenant"], "20.1 1.6 16.2": ["rotaxane"], "16.2 10.6 23.1": ["blader"], "4.7 21.9 15.5": ["diggity"], "2.6 0.6 14.2": ["scb"], "-4.7 36.7 6.0": ["muqawama"], "4.3 -6.1 10.4": ["androsterone"], "6.4 9.8 4.9": ["aktuelle"], "12.2 5.0 14.1": ["batiste"], "10.1 15.7 21.7": ["wingsail"], "6.2 6.4 7.5": ["mente"], "3.1 0.2 15.9": ["corff"], "11.7 7.0 15.1": ["powerwashed"], "7.8 -4.1 10.5": ["malalaking"], "16.1 -2.6 25.0": ["perogi"], "11.8 0.0 9.1": ["graphiques"], "-5.8 13.0 -1.1": ["overdramatization"], "4.6 6.5 14.0": ["rouching"], "3.6 13.4 14.1": ["cerebri"], "-7.2 16.9 6.7": ["answe"], "15.8 -5.7 16.5": ["marmoleum"], "-6.0 2.5 4.0": ["hyperreactivity"], "8.4 24.9 11.2": ["charnel"], "3.9 2.8 13.6": ["exeter"], "-1.0 16.0 18.4": ["karti"], "20.1 6.2 18.8": ["dromaeosaurid"], "5.1 0.5 -5.6": ["nonaspirin"], "3.3 20.2 3.5": ["defens"], "-5.7 4.7 12.7": ["basehan"], "10.4 14.0 22.4": ["tweedle"], "11.6 12.2 5.3": ["hosannahs"], "4.2 2.3 3.0": ["exajoules"], "11.6 21.1 14.6": ["tooldial"], "9.5 -5.9 26.4": ["comte"], "0.4 5.0 13.3": ["scorephone"], "-4.6 8.1 4.0": ["termi"], "-1.0 13.9 8.6": ["variceal"], "1.3 0.6 4.9": ["eul"], "0.3 7.8 1.0": ["piquetero"], "10.1 11.1 18.1": ["crystallite"], "2.1 17.2 10.5": ["singlemost"], "18.8 -0.6 -2.2": ["ultracentrifuge"], "2.5 0.9 10.6": ["frere"], "-3.2 10.2 7.5": ["elias"], "4.4 4.4 1.0": ["coverholder"], "10.7 14.4 10.2": ["allotrope"], "-3.9 5.0 2.8": ["msr"], "3.9 3.0 1.9": ["epartment"], "12.3 6.1 -1.5": ["zugu"], "-7.9 2.6 0.2": ["yle"], "5.9 10.3 1.1": ["permisson"], "8.5 20.8 6.2": ["lynches"], "8.2 8.6 17.8": ["gool"], "13.6 5.1 13.8": ["furst"], "5.9 2.1 3.9": ["visitthe"], "9.2 21.0 11.1": ["thoght"], "-2.0 7.3 13.1": ["leucocyte"], "15.7 8.5 31.4": ["tikkis"], "-5.3 -1.3 14.9": ["darby"], "16.4 8.6 11.5": ["shagpile"], "9.5 7.4 1.4": ["dyev"], "3.2 12.4 15.5": ["fallon"], "-4.9 10.6 6.6": ["costimulation"], "1.7 9.6 9.6": ["rado"], "9.5 3.7 12.5": ["rious"], "0.5 4.0 13.4": ["aglycone"], "1.7 17.0 7.7": ["biphobia"], "12.9 27.0 15.4": ["grapnels"], "4.6 4.8 1.5": ["ilke"], "9.1 3.9 9.2": ["randolph"], "-0.5 6.8 7.7": ["bleg"], "3.9 13.7 1.9": ["chemotypes"], "7.7 2.0 16.0": ["gioco"], "0.5 21.8 0.9": ["undoings"], "8.2 -2.3 13.6": ["orch"], "6.1 10.6 10.6": ["phata"], "0.6 10.4 -0.3": ["darf"], "4.8 6.7 12.7": ["etapa"], "2.1 1.5 1.4": ["streeter"], "2.9 6.0 5.2": ["ernment"], "4.7 -2.3 10.8": ["tunity"], "10.5 4.0 12.4": ["suivre"], "8.0 1.6 14.1": ["shetland"], "4.3 15.9 15.6": ["woolliest"], "1.3 15.9 2.2": ["criminalistic"], "17.1 -5.9 3.5": ["resultaten"], "20.5 6.0 10.0": ["micromotor"], "10.3 8.1 20.5": ["hillfort"], "0.3 19.1 0.9": ["injuria"], "13.9 -0.3 2.5": ["susbcribers"], "2.4 -2.7 -1.4": ["stamford"], "8.1 11.2 14.9": ["megafloods"], "-10.6 12.6 9.5": ["nondetectable"], "5.3 5.1 1.6": ["essentiellement"], "-2.5 -7.1 1.9": ["introduc"], "-1.8 6.7 3.3": ["professiona"], "6.7 10.2 12.3": ["bargraph"], "7.4 8.9 10.0": ["nanohorns"], "10.0 6.0 10.4": ["natrual"], "-6.9 15.5 10.0": ["epicentral"], "9.2 0.4 4.3": ["utiliza"], "-1.0 4.1 5.4": ["multibyte"], "11.7 7.9 23.7": ["rashy"], "5.3 8.8 10.8": ["baithaks"], "7.9 21.7 5.6": ["mantrips"], "16.2 13.5 11.6": ["metallically"], "9.1 4.7 22.8": ["shortsea"], "15.0 14.7 6.8": ["photoflash"], "4.0 7.3 12.9": ["exis"], "5.1 4.6 15.5": ["waaa"], "2.4 23.9 -2.9": ["causations"], "6.1 10.5 8.1": ["papillomaviruses"], "8.0 18.0 0.2": ["aggrandising"], "0.9 4.8 6.6": ["ataque"], "1.2 5.4 -0.7": ["informat"], "8.2 10.1 1.7": ["leafletted"], "19.8 17.0 21.6": ["faceplants"], "14.2 19.3 7.1": ["mongered"], "5.6 6.5 11.5": ["altissimo"], "9.1 8.2 10.4": ["prodynorphin"], "-0.6 7.7 11.9": ["haseen"], "4.6 28.0 5.6": ["conspiratory"], "4.2 9.1 5.3": ["downconverting"], "4.4 15.3 5.7": ["shruti"], "-2.7 7.2 7.5": ["shoaib"], "2.2 1.3 9.1": ["vaginalis"], "17.2 16.8 14.4": ["metronatural"], "11.2 11.4 16.3": ["nonnutritive"], "27.6 23.5 28.7": ["raptorial"], "12.4 2.8 14.3": ["sucres"], "12.6 14.7 43.2": ["bottlenoses"], "6.8 10.7 15.0": ["prai"], "9.9 5.0 13.7": ["nonwood"], "-9.1 -10.0 -0.8": ["rogram"], "6.0 26.9 8.4": ["intolerants"], "2.3 -3.1 5.2": ["velopment"], "-12.2 -3.1 -0.4": ["metabolizer"], "8.1 10.0 22.3": ["scablands"], "2.4 -4.8 14.6": ["tallahassee"], "-3.6 16.3 -5.7": ["aircraftsman"], "6.9 8.3 9.3": ["contenido"], "9.9 4.7 16.7": ["estimat"], "-0.6 9.5 14.5": ["dedi"], "-1.0 -0.7 8.8": ["rder"], "-5.0 5.0 7.4": ["tcl"], "8.1 3.7 19.6": ["monzonitic"], "1.9 -4.3 7.5": ["worki"], "-3.1 6.9 13.9": ["edukasyon"], "15.6 12.0 7.0": ["turne"], "11.3 7.7 -1.0": ["unrepayable"], "14.6 11.6 10.4": ["powerstrip"], "-1.3 11.0 7.4": ["nonrecoverable"], "14.5 18.9 0.1": ["katleen"], "18.0 8.4 6.3": ["elysian"], "-2.2 -5.3 -1.1": ["ibility"], "6.1 0.3 13.1": ["garten"], "2.6 8.6 21.6": ["folkclub"], "0.9 8.9 1.4": ["bollywooddivas"], "6.8 6.2 5.1": ["fortwos"], "14.6 5.8 35.5": ["chowchow"], "-0.5 0.2 4.0": ["amico"], "7.4 20.9 17.5": ["shrinkers"], "6.8 7.5 10.8": ["metatarsus"], "1.7 1.5 28.0": ["gulfside"], "-4.3 5.9 14.3": ["tinanggap"], "7.1 -1.4 6.9": ["processeurs"], "14.7 6.7 29.4": ["fragrans"], "6.7 -0.2 5.8": ["compagnies"], "12.2 5.4 30.8": ["buche"], "4.2 0.9 14.7": ["mediante"], "3.8 -1.6 6.9": ["threadcount"], "7.4 4.0 13.0": ["sheesham"], "6.6 14.3 12.6": ["outwaiting"], "6.9 -9.1 2.2": ["uear"], "14.1 8.8 8.3": ["metafile"], "5.2 -1.8 4.8": ["vertabra"], "1.6 -1.3 11.4": ["cve"], "11.6 -0.9 17.4": ["cyalis"], "-6.8 6.0 1.6": ["myelosuppressive"], "13.8 7.1 12.2": ["schwarz"], "15.5 9.1 3.6": ["omy"], "-3.0 5.3 6.1": ["lucinactant"], "2.8 14.5 18.7": ["coryza"], "10.0 7.7 15.8": ["hydrogenate"], "18.7 23.9 11.9": ["vader"], "16.2 -2.7 29.3": ["neapolitan"], "10.9 24.4 11.9": ["pogue"], "5.9 4.6 2.7": ["ribonucleoprotein"], "-9.1 6.5 5.9": ["overdiagnosing"], "1.1 3.6 12.5": ["marko"], "13.3 16.3 26.0": ["unironed"], "-5.1 -2.4 -2.4": ["entral"], "5.1 -1.0 8.2": ["turno"], "-2.2 2.2 2.4": ["nized"], "3.9 -0.7 10.3": ["erythropoeitin"], "0.9 1.2 1.3": ["aclaimed"], "5.4 8.9 15.0": ["nucleocapsid"], "2.8 2.5 5.5": ["subacromial"], "3.2 9.6 -2.2": ["preboard"], "9.2 6.0 27.8": ["turqoise"], "10.8 4.6 25.1": ["cotta"], "-0.1 -0.6 15.4": ["patuloy"], "2.5 7.9 4.6": ["rackmounts"], "9.4 19.7 9.9": ["oratorically"], "11.1 6.8 11.3": ["tiga"], "-5.1 19.2 9.4": ["irespective"], "8.4 12.7 -3.1": ["hearbeat"], "-4.5 0.5 -2.0": ["renoprotective"], "-2.5 3.3 12.6": ["sakaling"], "-1.0 7.1 11.4": ["ginamit"], "20.7 9.2 38.9": ["sunomono"], "-0.5 13.9 -6.2": ["coequals"], "6.9 2.2 12.5": ["hsia"], "11.6 3.1 13.5": ["tela"], "4.4 -1.6 6.4": ["photopolymers"], "8.1 1.3 14.1": ["omi"], "-1.9 4.1 14.0": ["reassortants"], "-1.8 5.9 23.1": ["tutin"], "10.1 10.8 4.7": ["neigbhorhood"], "7.1 15.4 12.6": ["utak"], "13.7 5.4 8.4": ["cryocoolers"], "11.4 21.7 -3.4": ["totalistic"], "-3.3 1.3 15.2": ["ayusin"], "7.4 14.2 5.8": ["paranormalist"], "5.5 12.3 7.7": ["asmita"], "1.3 -2.5 8.4": ["latimes"], "3.7 10.6 13.3": ["betwe"], "10.1 6.5 32.5": ["ryori"], "6.4 22.8 -2.9": ["enciphered"], "8.1 -5.6 19.3": ["basketed"], "0.3 13.7 11.7": ["scaldings"], "8.3 14.6 15.2": ["haaaa"], "1.7 -2.0 9.0": ["tutte"], "2.2 -2.4 3.5": ["prokinetic"], "3.8 16.4 -7.8": ["instution"], "3.0 9.0 7.6": ["chote"], "9.6 7.3 9.6": ["vagabonding"], "9.1 11.4 6.2": ["retrocyclin"], "6.4 11.0 16.8": ["tomm"], "11.1 0.8 8.6": ["ganado"], "10.3 2.7 14.0": ["pocos"], "12.5 17.2 15.7": ["evenually"], "10.6 10.1 14.1": ["responsabilidad"], "6.3 0.0 9.6": ["agor"], "1.7 -1.3 5.7": ["optica"], "2.3 9.4 6.9": ["polyphenylsulfone"], "16.1 -9.8 2.7": ["geoenvironmental"], "3.6 4.5 10.0": ["fluorochrome"], "14.0 5.4 3.4": ["opportunit"], "7.6 6.4 13.7": ["branson"], "14.7 -3.4 16.8": ["maire"], "13.9 7.3 26.3": ["chena"], "-6.0 -4.5 8.6": ["clobetasol"], "4.0 9.8 9.4": ["jmt"], "16.0 10.6 20.8": ["longa"], "-11.4 11.9 4.1": ["leges"], "5.3 4.5 16.0": ["canceller"], "5.1 -2.8 19.0": ["ferrier"], "3.1 20.3 7.0": ["janissary"], "12.3 3.6 29.9": ["nonrefrigerated"], "-3.6 12.5 2.6": ["assistors"], "-0.8 1.7 6.3": ["arevery"], "12.3 14.8 6.4": ["yolked"], "-0.1 6.3 3.0": ["interno"], "9.1 1.5 4.6": ["derniers"], "2.1 -0.6 19.0": ["saeng"], "7.4 20.8 16.1": ["guardia"], "5.6 10.1 15.8": ["hablo"], "4.5 1.7 7.5": ["ppy"], "22.3 14.3 21.3": ["mukluk"], "13.2 9.6 6.4": ["bioelectronic"], "0.6 -0.1 8.5": ["aia"], "9.8 7.6 5.6": ["jena"], "1.4 -4.9 7.6": ["vento"], "13.1 -1.4 34.4": ["nonfried"], "9.3 -3.3 7.3": ["bedrijf"], "9.8 8.5 13.7": ["metamerism"], "1.7 18.8 4.6": ["incapabilities"], "2.9 2.4 -6.9": ["ocr"], "19.8 16.6 30.5": ["amanita"], "1.4 -3.4 8.2": ["busnes"], "-0.4 -1.4 8.7": ["rek"], "-3.9 -9.1 -2.1": ["ission"], "6.6 3.2 7.6": ["mies"], "12.2 -0.8 23.4": ["bloomy"], "8.6 2.3 32.1": ["shortribs"], "13.7 -3.2 14.8": ["rena"], "19.3 9.8 11.1": ["steelbook"], "3.5 3.3 6.9": ["heen"], "7.0 9.7 14.2": ["insolubles"], "8.2 8.3 20.9": ["implique"], "14.6 14.6 9.6": ["retroreflector"], "-1.3 3.3 -0.3": ["zik"], "-0.7 12.5 9.6": ["outhustles"], "-5.1 8.6 4.7": ["facilitatory"], "6.2 -0.3 8.2": ["bdrms"], "5.5 10.5 24.2": ["hwe"], "7.7 10.5 11.6": ["anerobic"], "-0.8 5.9 7.9": ["paren"], "-2.8 22.3 -2.6": ["passivism"], "-1.5 9.0 5.4": ["banaya"], "4.5 -2.7 6.8": ["vuelve"], "11.5 3.8 6.3": ["taggable"], "13.8 -0.4 11.9": ["giochi"], "7.9 6.3 8.5": ["mejora"], "-4.3 0.0 -2.0": ["educat"], "5.5 12.9 12.9": ["kanaka"], "6.2 13.4 24.3": ["moschata"], "-1.7 10.1 9.6": ["shotokan"], "0.1 9.7 11.5": ["equimolar"], "5.4 15.9 9.3": ["seeeded"], "22.0 10.1 9.5": ["protoplanetary"], "10.1 16.5 10.3": ["nameable"], "15.3 28.7 4.3": ["nationless"], "1.8 5.1 -1.4": ["minimizers"], "9.5 -2.8 -2.8": ["campeones"], "9.2 5.1 9.1": ["glitteratti"], "4.3 0.8 5.4": ["statu"], "2.1 -1.8 5.1": ["shif"], "-10.4 4.8 7.8": ["dft"], "20.0 -2.3 -1.2": ["imagewear"], "8.1 6.6 18.4": ["verticillata"], "7.9 3.7 10.0": ["gluteoplasty"], "11.0 2.2 8.2": ["votar"], "7.5 -3.3 10.0": ["steamfield"], "4.2 -0.1 14.5": ["dejar"], "12.3 10.6 14.1": ["galabeya"], "15.2 6.6 17.6": ["ciwujia"], "1.2 10.5 2.0": ["rechts"], "-2.0 5.6 13.9": ["ghoda"], "8.0 16.7 8.1": ["unsureness"], "-4.0 3.4 6.2": ["histopathologist"], "-0.4 14.1 14.8": ["ctc"], "8.9 2.9 2.7": ["zweiten"], "-2.4 -3.5 15.6": ["mawawala"], "-1.2 -3.7 2.7": ["toobtain"], "18.1 14.6 16.1": ["nourisher"], "9.2 3.2 20.0": ["necker"], "25.3 7.6 19.7": ["jumbies"], "1.3 11.2 21.5": ["khane"], "-1.7 6.8 8.2": ["sensorineural"], "-11.6 8.8 8.0": ["alleviations"], "-1.8 -0.0 2.6": ["geropsychiatric"], "17.9 -3.7 9.1": ["jointless"], "28.3 20.0 27.1": ["komodo"], "4.6 4.1 6.0": ["etudiant"], "2.6 -1.8 12.1": ["consejos"], "-1.4 7.7 10.7": ["paragneisses"], "-3.8 6.7 4.2": ["pseudotumor"], "10.4 14.1 12.3": ["cultishly"], "16.4 2.6 20.2": ["paids"], "11.5 2.5 17.8": ["bix"], "3.6 9.8 12.5": ["overboosted"], "0.0 -2.7 -1.1": ["davos"], "8.7 0.9 16.4": ["melrose"], "7.8 13.9 6.9": ["pawar"], "3.5 12.0 18.4": ["tubbing"], "6.0 7.3 9.1": ["puedan"], "9.1 6.2 10.6": ["sidelites"], "6.4 7.5 21.3": ["artisanally"], "5.3 15.0 10.0": ["democracia"], "-6.8 6.1 2.9": ["examin"], "2.8 5.3 3.9": ["ophthalmoscopy"], "16.4 17.1 13.5": ["aishwarya"], "-1.0 3.7 16.3": ["tified"], "2.2 2.0 14.4": ["fluorotelomer"], "1.3 12.5 8.9": ["vish"], "8.7 19.6 19.1": ["thiago"], "13.9 2.2 0.3": ["amoritization"], "8.5 10.2 5.5": ["citta"], "10.4 7.7 14.2": ["peste"], "3.9 11.6 12.0": ["sogar"], "-2.5 8.0 10.1": ["tellurides"], "14.8 6.0 0.6": ["explosed"], "12.3 5.1 11.3": ["aeroderivative"], "1.3 -1.6 17.4": ["lemberger"], "15.6 -4.6 16.4": ["duluth"], "2.1 -1.6 4.6": ["photocoupler"], "6.5 11.4 2.5": ["smeargate"], "-5.9 -8.0 3.8": ["tutions"], "2.6 6.6 6.9": ["antidepression"], "11.2 -3.8 12.1": ["aircrete"], "-2.6 0.9 2.5": ["idtheft"], "-3.9 12.5 5.4": ["afridi"], "9.1 3.1 18.6": ["formas"], "-1.7 -0.3 6.3": ["industriel"], "18.2 14.3 13.6": ["rumblin"], "18.4 7.7 15.0": ["hurdy"], "3.5 0.9 -4.9": ["redit"], "6.4 0.7 9.1": ["ssr"], "2.1 4.1 16.7": ["maaga"], "2.6 6.4 8.9": ["mauvaise"], "7.3 -1.4 31.3": ["kabuli"], "19.8 17.2 11.0": ["oopsy"], "12.4 2.7 5.9": ["pressurizers"], "4.8 -1.0 16.3": ["sixteens"], "8.2 2.9 7.1": ["genug"], "11.2 -1.7 0.4": ["cbr"], "-5.4 4.1 4.7": ["equipotent"], "-6.4 1.3 -2.7": ["esting"], "10.9 4.8 17.8": ["sunflowerseed"], "11.0 -1.6 -3.5": ["reinitiates"], "12.6 -3.6 4.2": ["developpement"], "13.3 4.1 12.8": ["soluable"], "8.0 6.2 12.9": ["ladi"], "1.3 15.6 7.6": ["wordcraft"], "11.1 4.1 4.7": ["nextevolution"], "5.4 -2.5 2.0": ["gogreen"], "-7.8 11.7 -0.7": ["vanni"], "6.7 12.1 10.0": ["singal"], "-0.7 0.1 16.0": ["counteroffered"], "11.9 6.3 21.7": ["varial"], "17.7 6.7 19.7": ["downard"], "15.6 7.0 19.5": ["granulosa"], "16.0 9.2 6.5": ["middecade"], "14.5 11.6 14.8": ["technopop"], "2.8 13.3 14.1": ["widsom"], "7.1 10.0 6.2": ["amongt"], "9.3 4.6 21.1": ["dbh"], "8.7 1.8 29.7": ["rapa"], "3.8 -2.6 11.7": ["crystallizer"], "-1.5 13.4 9.6": ["promethium"], "9.1 -2.8 13.2": ["lipslide"], "-2.3 22.0 -0.7": ["eidetic"], "-5.3 5.9 -1.4": ["havurah"], "17.7 5.7 2.3": ["creen"], "-0.7 -1.9 10.6": ["jani"], "13.4 2.7 -0.8": ["countercomplaint"], "2.3 0.4 8.8": ["prie"], "14.6 5.0 8.8": ["stal"], "12.3 3.8 17.7": ["nanolayer"], "2.2 5.3 5.1": ["wps"], "-2.8 2.2 6.5": ["hemangioblast"], "8.1 -5.3 -6.3": ["exeuctive"], "3.9 6.3 10.0": ["laufen"], "9.1 -2.0 10.7": ["ceisio"], "5.7 -3.2 -0.4": ["upc"], "4.7 1.0 11.2": ["marriagelike"], "13.4 34.6 15.9": ["aimpoint"], "10.5 4.6 5.0": ["utiliser"], "-4.8 -6.5 6.6": ["folles"], "14.1 27.0 16.1": ["masterless"], "18.5 5.6 22.8": ["stylie"], "-6.6 14.1 7.8": ["hemodynamically"], "0.7 4.3 -11.7": ["hicago"], "-2.2 23.3 17.8": ["nons"], "16.3 -2.0 4.6": ["nsurance"], "9.5 7.2 6.1": ["exclu"], "0.1 3.4 -2.6": ["elbion"], "0.8 3.1 6.2": ["individua"], "12.5 -0.5 31.9": ["melba"], "8.9 12.9 10.4": ["gure"], "4.8 5.3 10.5": ["markable"], "7.8 7.8 17.4": ["stockwater"], "7.8 12.4 48.4": ["trochus"], "3.4 8.2 -0.9": ["kommenden"], "0.7 1.2 11.8": ["uwi"], "-5.2 0.5 4.2": ["emption"], "4.9 2.1 16.6": ["kalimantanensis"], "1.4 -4.8 0.5": ["ohl"], "7.8 8.8 0.4": ["electromotive"], "8.1 7.6 16.0": ["risus"], "3.5 -3.3 -0.5": ["scientifiques"], "13.7 28.4 7.1": ["jackings"], "12.1 2.2 11.7": ["geopolymer"], "-3.7 2.9 14.5": ["ayos"], "1.5 2.1 15.4": ["usab"], "3.1 11.6 12.7": ["bottomhole"], "17.4 8.8 6.7": ["aisled"], "9.7 9.0 33.2": ["milanese"], "3.1 22.0 1.4": ["warrentless"], "-1.7 26.6 5.8": ["rcmp"], "1.0 10.5 5.1": ["tricameral"], "6.7 7.4 6.7": ["instates"], "2.5 -6.4 10.9": ["mehn"], "-0.5 9.0 4.5": ["soient"], "6.5 -3.5 16.3": ["interesterification"], "-1.5 11.3 14.9": ["externa"], "10.3 10.0 8.7": ["snakebyte"], "-7.1 3.9 0.8": ["shibir"], "-0.6 12.6 6.8": ["extracapsular"], "4.6 -1.8 -0.3": ["versiones"], "-4.3 -4.7 9.6": ["polydipsia"], "10.4 1.4 3.4": ["lettres"], "-0.3 9.2 3.1": ["liebe"], "2.4 9.5 3.7": ["columna"], "0.0 1.9 9.8": ["annu"], "6.7 2.1 7.7": ["tienes"], "4.5 8.4 7.1": ["adversly"], "3.2 2.5 11.2": ["motrin"], "27.3 15.2 13.3": ["superbanks"], "6.9 -0.5 20.2": ["cortado"], "10.0 15.0 34.7": ["vaquitas"], "6.5 11.2 9.6": ["iaculis"], "17.3 13.6 15.2": ["huelga"], "-5.9 13.2 0.5": ["desribe"], "2.6 0.2 8.1": ["concordia"], "0.8 2.6 16.5": ["aari"], "10.2 25.1 11.9": ["shabbiha"], "-2.6 0.2 0.3": ["choregrapher"], "4.6 22.7 0.1": ["vetronics"], "3.9 7.3 13.3": ["legspinning"], "6.4 16.3 11.4": ["sequent"], "8.1 3.1 9.1": ["magnocellular"], "8.6 13.3 17.2": ["vl"], "4.2 22.9 2.0": ["servents"], "12.3 21.7 9.8": ["judaize"], "3.4 5.2 12.6": ["wellwater"], "6.9 7.6 11.0": ["nates"], "-0.8 3.5 28.1": ["bakar"], "12.5 7.8 15.7": ["neste"], "-7.2 -2.3 -1.4": ["rson"], "17.5 13.9 17.5": ["flimflams"], "-0.8 1.7 16.5": ["ibibigay"], "12.3 4.5 12.5": ["fuga"], "3.3 12.0 8.1": ["antipoaching"], "3.9 28.6 5.7": ["karzai"], "7.5 11.0 8.5": ["polymyxin"], "10.4 -2.6 3.9": ["rosed"], "17.3 11.8 18.7": ["hoppiest"], "16.1 8.9 -3.3": ["megapastor"], "3.0 17.0 1.2": ["gamuts"], "-1.4 2.4 0.3": ["chasa"], "0.8 -10.5 -1.8": ["ebs"], "8.4 -7.7 9.2": ["eyescreen"], "-5.0 -6.0 -1.1": ["achie"], "15.7 8.6 19.6": ["regilded"], "11.7 8.6 11.8": ["pling"], "4.8 4.8 7.7": ["levelised"], "7.1 1.1 14.4": ["nesaf"], "-7.4 3.3 12.3": ["simons"], "0.5 10.8 6.7": ["heem"], "8.1 11.2 0.2": ["greasemonkey"], "4.9 13.1 20.6": ["paese"], "9.6 9.7 5.5": ["freakery"], "-4.2 4.7 9.5": ["personnages"], "8.7 10.9 41.2": ["gefilte"], "0.5 14.8 8.8": ["monofocal"], "-2.1 9.0 10.9": ["osis"], "1.0 8.8 27.7": ["mulato"], "8.2 9.4 12.4": ["autant"], "3.9 14.9 6.0": ["mentis"], "25.0 0.5 16.0": ["multihead"], "13.7 9.7 40.1": ["liempo"], "8.6 5.5 10.9": ["ventaja"], "-2.5 6.2 1.6": ["ipso"], "10.2 9.5 16.3": ["feetfirst"], "10.2 3.8 11.4": ["pilote"], "12.7 -0.2 9.7": ["construit"], "12.7 7.9 10.6": ["viharas"], "-3.0 -6.7 13.8": ["kiba"], "4.6 -3.3 0.2": ["inr"], "-2.0 5.0 10.2": ["policiers"], "12.7 2.9 6.0": ["newsers"], "6.2 3.0 -0.4": ["incadea"], "13.5 -13.2 10.2": ["enth"], "6.0 17.3 -1.7": ["patriated"], "13.6 11.9 19.0": ["mamaw"], "7.8 3.5 9.6": ["dispositivos"], "6.4 3.8 12.2": ["nandralone"], "-1.9 -2.0 2.3": ["variate"], "7.8 11.9 6.2": ["metreage"], "5.5 -2.7 6.9": ["tist"], "8.3 6.4 18.8": ["barbatus"], "5.6 9.5 9.9": ["superally"], "-12.8 8.1 -6.0": ["psychoanalytically"], "9.2 2.3 4.2": ["bbm"], "5.8 5.5 11.6": ["swyddogion"], "4.8 -2.0 13.3": ["pruebas"], "3.0 1.2 11.9": ["jalo"], "7.1 -5.3 14.3": ["sussex"], "11.7 -1.8 5.9": ["polysiloxane"], "-3.7 -3.0 9.7": ["neurohormone"], "2.4 -0.8 4.1": ["cascadable"], "4.9 4.3 5.1": ["hroughout"], "5.6 5.8 12.6": ["suprarenal"], "6.0 4.1 9.2": ["smallbiz"], "20.0 9.4 20.7": ["hummocky"], "13.5 10.1 13.8": ["acest"], "11.3 2.8 4.9": ["unmortgaged"], "11.9 4.9 17.1": ["flanagan"], "3.9 7.5 4.6": ["arcmin"], "3.3 7.5 1.3": ["bernstein"], "6.5 23.8 7.9": ["plainsclothes"], "10.4 8.6 7.1": ["koda"], "2.9 -3.1 7.3": ["bodypainted"], "19.0 25.4 31.2": ["defoliators"], "-2.3 -12.3 2.0": ["cates"], "2.5 -4.5 4.7": ["quarterended"], "-3.0 -0.2 -1.6": ["ommittee"], "18.5 7.5 33.4": ["huia"], "6.9 6.8 2.6": ["pneumo"], "-5.6 15.9 2.3": ["leitmotivs"], "17.1 23.5 20.8": ["dragonball"], "-2.7 -11.8 6.5": ["duced"], "6.1 -3.1 14.1": ["achub"], "3.1 5.1 -0.9": ["arteritis"], "4.5 15.9 1.3": ["unsportmanlike"], "11.5 10.6 7.9": ["crear"], "11.4 10.5 19.4": ["oikos"], "11.2 2.5 7.9": ["ngland"], "11.5 4.8 12.4": ["nibbed"], "11.8 12.1 22.3": ["nitida"], "9.2 4.3 8.1": ["rdesktop"], "-1.7 4.4 -3.2": ["webisodic"], "6.9 14.5 2.2": ["dominican"], "0.6 -5.3 2.8": ["paign"], "10.1 7.9 13.5": ["tattersall"], "10.1 3.8 17.9": ["verti"], "4.3 1.6 3.6": ["bcpbank"], "12.5 6.3 9.8": ["acteurs"], "2.2 -3.4 2.8": ["rida"], "17.4 -0.1 18.3": ["dilapitated"], "8.8 20.9 15.0": ["thumbless"], "4.9 -0.4 34.5": ["nontidal"], "-3.5 -14.5 4.7": ["anuary"], "-1.8 -0.9 11.6": ["westnile"], "2.4 6.3 14.3": ["homogenates"], "-3.5 9.9 3.9": ["arres"], "36.4 4.1 10.5": ["skyrise"], "-1.0 1.0 2.7": ["nigrostriatal"], "7.0 -4.3 12.2": ["dwntwn"], "4.9 2.1 12.4": ["quebecoise"], "-2.6 9.2 11.5": ["kafi"], "10.6 11.3 26.0": ["maculatum"], "1.5 9.2 1.1": ["raus"], "12.4 27.2 17.0": ["panoramically"], "10.9 0.5 11.3": ["prensa"], "-1.9 2.7 12.7": ["maoy"], "15.5 10.2 7.3": ["instamatic"], "5.4 19.3 13.3": ["devolutionists"], "2.6 5.9 11.9": ["veulent"], "-8.5 6.8 4.2": ["signors"], "8.5 8.6 19.8": ["teers"], "1.4 5.3 18.6": ["jata"], "11.2 4.3 30.1": ["spag"], "14.9 1.6 9.0": ["gress"], "-5.2 -2.5 1.8": ["ordinator"], "13.6 11.7 35.2": ["cowrie"], "8.3 14.1 13.0": ["kote"], "-0.2 0.3 11.6": ["raff"], "4.7 1.8 10.4": ["monosodium"], "11.8 4.6 23.7": ["gac"], "8.4 2.6 3.3": ["neuroinformatics"], "5.4 2.6 7.3": ["ipt"], "1.6 12.8 5.1": ["ductus"], "20.3 22.0 30.2": ["seafloors"], "-1.0 1.8 5.7": ["owski"], "-5.9 -9.8 13.6": ["lohs"], "11.4 9.6 19.6": ["yote"], "13.3 6.0 -1.8": ["michaelianblack"], "8.2 17.2 9.6": ["peuple"], "18.9 2.7 11.9": ["nanofabric"], "7.9 2.0 8.1": ["automne"], "-0.9 2.3 13.1": ["gagawa"], "0.8 0.4 -5.0": ["tect"], "0.5 0.8 20.4": ["soupe"], "-13.9 -0.1 4.5": ["interp"], "3.1 5.7 23.5": ["arca"], "2.1 11.7 13.6": ["rainwaters"], "-11.2 -3.5 -2.5": ["xecutive"], "4.5 2.1 9.9": ["maximo"], "21.4 26.2 15.4": ["wascally"], "4.8 5.8 11.2": ["marquardt"], "13.0 15.3 18.2": ["slicken"], "16.8 11.0 8.6": ["multiprong"], "14.3 10.6 27.9": ["swizzles"], "-5.2 3.2 7.2": ["tibiofemoral"], "12.6 12.5 10.8": ["larga"], "11.2 17.3 10.8": ["rooftoops"], "10.0 6.2 9.7": ["sherlock"], "15.1 8.5 14.4": ["tft"], "3.5 12.8 5.2": ["sketchwriters"], "12.7 18.8 9.8": ["plutoed"], "2.4 -6.8 4.8": ["roduction"], "11.7 2.9 10.3": ["coachella"], "-6.1 7.7 13.1": ["tagumpay"], "4.3 10.3 13.4": ["comentarios"], "7.8 18.1 9.1": ["malis"], "-2.0 8.1 22.8": ["perilipin"], "3.0 2.6 5.8": ["gemeinsam", "taggle"], "3.7 9.2 15.5": ["epees"], "5.6 12.0 11.5": ["ghi"], "-1.7 -1.6 12.1": ["tsang"], "11.5 3.9 25.6": ["teleost"], "15.6 -4.5 14.9": ["sheek"], "10.4 6.8 14.5": ["earthtone"], "12.7 26.6 19.5": ["alrighty"], "-0.5 5.1 25.3": ["rabbiteye"], "13.9 7.6 21.8": ["rickey"], "8.5 11.3 9.8": ["publik"], "4.6 1.0 17.0": ["palmitoleate"], "19.7 4.4 31.9": ["inari"], "22.3 11.5 25.6": ["moorish"], "13.7 -4.5 21.3": ["tailslide"], "7.4 7.1 19.5": ["skyramp"], "-3.7 4.2 6.3": ["lando"], "2.5 4.7 -1.0": ["ministro"], "6.4 0.9 -2.0": ["deregisters"], "14.5 9.5 7.6": ["headine"], "5.8 10.1 12.6": ["unplastered"], "21.8 16.0 39.5": ["elodea"], "17.3 -0.0 17.4": ["skoopz"], "8.2 16.5 11.7": ["umbilically"], "12.9 5.3 12.6": ["gatos"], "4.2 0.5 14.9": ["ddweud"], "3.5 15.6 -3.1": ["explict"], "4.7 8.5 30.9": ["agrodolce"], "-2.4 5.9 3.4": ["karni"], "-0.2 3.9 15.6": ["buti"], "20.5 19.6 33.8": ["bloodsicles"], "-9.3 -1.5 7.1": ["treasuer"], "6.8 7.6 6.3": ["outpassing"], "13.7 18.8 4.2": ["magnons"], "9.4 8.2 -2.8": ["certgate"], "24.5 11.2 9.2": ["tweel"], "1.5 11.5 4.0": ["nonoffending"], "12.6 0.5 19.0": ["parure"], "6.6 -1.4 -1.8": ["superspeciality"], "5.9 6.7 15.0": ["ostia"], "5.7 15.7 9.1": ["pardesi"], "0.0 -6.6 -5.3": ["quadripolar"], "-3.4 26.6 2.9": ["nonbattle"], "3.2 10.4 16.5": ["ayon"], "1.4 8.6 19.1": ["midshaft"], "12.2 5.9 13.7": ["diversos"], "10.2 -2.1 12.8": ["nextday"], "4.4 14.5 4.2": ["webkey"], "-11.8 -13.9 0.9": ["eby"], "6.8 17.1 4.6": ["coupmakers"], "1.5 9.7 16.4": ["baras"], "-4.7 14.1 8.3": ["lipi"], "8.2 10.7 19.2": ["hansom"], "26.7 11.6 7.8": ["stichting"], "3.3 2.8 7.0": ["qemu"], "12.8 7.1 13.3": ["markered"], "3.8 1.7 9.4": ["feasiblity"], "-1.2 10.3 8.2": ["sitcomish"], "10.6 -1.0 3.9": ["dividende"], "19.2 4.4 19.3": ["pontil"], "-2.3 2.1 17.9": ["gic"], "11.4 -5.2 9.6": ["plana"], "-7.5 3.6 8.1": ["arents"], "13.9 6.1 17.9": ["bajos"], "2.2 18.3 5.3": ["annoymous"], "-6.6 2.6 -3.3": ["hidradenitis"], "-16.5 2.7 1.4": ["reme"], "-2.7 1.5 20.1": ["karera"], "3.1 -7.6 20.7": ["huacaya"], "13.5 -0.0 9.4": ["jeaned"], "-1.5 12.4 0.1": ["charset"], "-0.1 5.6 8.9": ["paulo"], "11.8 8.4 21.1": ["lobate"], "2.9 21.6 6.9": ["mutiliated"], "-7.0 14.2 -8.3": ["markaz"], "-0.6 0.4 10.8": ["imine"], "-1.5 34.4 3.6": ["attrited"], "8.9 0.4 31.2": ["bhatura"], "13.9 15.2 16.7": ["opertunity"], "7.3 -0.8 5.7": ["biggs"], "4.8 6.1 11.4": ["incurr"], "17.9 4.5 16.6": ["tightfitting"], "10.2 8.4 8.4": ["photomultipliers"], "8.7 3.1 1.2": ["desmodromic"], "7.7 4.5 3.1": ["perinatally"], "1.4 -2.0 14.1": ["funnylady"], "4.3 14.0 13.0": ["kahle"], "20.5 -2.5 21.4": ["maplewood"], "0.1 1.6 14.9": ["rangi"], "4.7 5.0 14.3": ["estados"], "11.3 -5.6 16.0": ["superieure"], "5.5 6.2 13.6": ["revista"], "6.1 0.1 9.5": ["segura"], "0.6 12.1 0.4": ["unrevoked"], "0.8 11.5 12.1": ["obturation"], "7.7 1.2 10.4": ["actifs"], "2.8 9.7 9.4": ["livingston"], "7.7 10.1 6.8": ["sover"], "18.7 5.7 6.9": ["paraphanalia"], "-5.7 4.9 4.2": ["sll"], "7.6 3.2 23.1": ["fiore"], "1.5 3.1 11.5": ["snowshowers"], "2.0 6.8 9.7": ["beses"], "1.6 5.0 2.5": ["microvolt"], "-0.3 0.9 13.3": ["antiobiotic"], "2.7 13.2 12.3": ["rehna"], "2.1 9.8 10.2": ["eeds"], "7.7 10.2 17.5": ["mouche"], "0.1 1.2 12.4": ["sance"], "1.2 7.9 14.6": ["immunocontraception"], "12.2 7.4 5.8": ["chaddis"], "-5.3 3.4 21.3": ["sville"], "3.9 18.1 17.5": ["rajniti"], "22.8 17.2 27.4": ["ripply"], "-2.2 2.0 8.1": ["articularly"], "9.5 1.6 9.2": ["funcionarios"], "26.3 6.7 38.7": ["gourami"], "11.0 3.7 18.9": ["gofal"], "6.2 0.6 18.5": ["cioccolato"], "3.9 11.1 12.9": ["longtemps"], "3.5 9.5 12.6": ["jodie"], "5.8 9.8 7.3": ["disapp"], "6.9 -1.0 13.5": ["lladd"], "13.3 7.4 24.2": ["destaffing"], "5.2 0.8 10.9": ["lished"], "15.5 5.0 17.0": ["styro"], "-2.6 -6.5 11.2": ["igher"], "5.8 9.7 10.3": ["trifoliate"], "0.3 13.3 12.7": ["tucky"], "6.7 6.0 16.3": ["klatches"], "3.0 6.3 11.7": ["reciente"], "8.3 -1.2 2.3": ["inds"], "4.8 1.8 -7.0": ["ecember"], "3.7 8.5 -0.8": ["aberrometer"], "21.8 1.4 33.9": ["shirataki"], "5.9 11.1 19.3": ["whoopings"], "12.5 3.8 25.2": ["gingelly"], "4.2 21.6 5.1": ["dysfunctionalities"], "21.1 5.1 15.9": ["pff"], "4.3 6.2 10.0": ["hydroperoxide"], "8.4 4.6 -1.3": ["hoever"], "2.0 -10.1 6.5": ["zhahn"], "22.1 21.3 27.0": ["walleyed"], "0.2 4.8 16.6": ["daahlings"], "-11.0 3.9 6.9": ["taba"], "9.9 -8.5 24.4": ["porc"], "15.2 5.3 12.5": ["swankest"], "0.9 7.4 14.3": ["puasa"], "3.3 8.4 16.4": ["ckin"], "0.9 9.8 3.0": ["unvouched"], "16.4 8.4 13.1": ["dcoios"], "16.8 9.4 8.2": ["promethean"], "7.1 5.2 3.6": ["legenday"], "1.5 8.5 14.4": ["rerollers"], "13.0 10.5 6.4": ["silverchair"], "9.3 4.3 11.9": ["southestern"], "5.4 12.1 3.1": ["fficial"], "10.2 6.0 5.8": ["dynamique"], "12.7 8.0 30.9": ["sili"], "4.4 -5.4 3.5": ["nomme"], "11.9 13.2 7.9": ["magnetospheres"], "3.0 9.5 12.4": ["nonabsorbable"], "4.6 14.5 14.7": ["malinois"], "4.7 4.0 7.6": ["lsquo"], "9.1 -1.5 8.4": ["perday"], "11.9 2.8 21.9": ["haricots"], "-2.6 16.6 4.5": ["dsps"], "1.1 34.6 9.3": ["harb"], "-3.5 4.2 4.2": ["phere"], "0.9 -12.3 10.1": ["tica"], "-2.2 7.8 9.8": ["tiwala"], "2.4 12.0 9.8": ["katiwalian"], "7.6 18.6 11.9": ["problemsolving"], "11.0 9.0 13.9": ["bhs"], "9.0 -1.9 4.0": ["bioerodible"], "4.3 5.7 5.6": ["newsflows"], "4.8 10.1 2.5": ["transcytosis"], "1.6 1.4 12.4": ["arwain"], "-0.2 8.7 7.5": ["suboptimally"], "7.6 3.1 7.6": ["traited"], "-3.0 5.6 15.4": ["homodimer"], "8.8 11.2 11.6": ["neighorhoods"], "-6.0 10.0 -2.0": ["amil"], "3.8 16.4 12.7": ["histolytica"], "7.9 1.3 14.9": ["sode"], "9.6 4.2 32.9": ["hardneck"], "16.0 14.6 7.8": ["multiplane"], "3.4 2.1 11.7": ["pontential"], "-7.6 6.9 10.5": ["nonseminoma"], "9.1 11.0 17.5": ["saam"], "-1.8 -7.9 14.9": ["alang"], "-2.5 20.5 8.0": ["confrontative"], "0.3 8.2 11.8": ["peux"], "-6.1 3.1 3.2": ["amdt"], "-1.1 -7.0 -2.0": ["expres"], "1.2 -11.3 -2.5": ["pacakage"], "5.5 2.4 12.7": ["farmettes"], "11.0 18.0 3.0": ["patrie"], "12.3 6.1 9.2": ["nytt"], "3.6 3.8 11.7": ["veux"], "7.2 18.9 20.1": ["coevolutionary"], "17.9 -0.7 8.1": ["kronas"], "-1.1 5.5 3.9": ["desmoplastic"], "-0.2 4.2 15.5": ["dokumento"], "9.4 7.0 16.9": ["diacritical"], "5.9 -0.5 15.2": ["planyourvisit"], "2.9 12.9 7.8": ["galti"], "25.0 12.3 21.9": ["waterplay"], "9.5 -2.3 12.7": ["bref"], "10.8 22.6 16.7": ["gutwrench"], "-2.1 7.7 13.2": ["stardate"], "14.6 3.7 14.1": ["oast"], "-6.8 11.5 3.9": ["tariq"], "-2.8 -2.1 -4.3": ["africaine"], "1.8 6.8 -5.1": ["chemoablation"], "-4.0 0.9 1.3": ["postdose"], "-2.2 -5.8 9.1": ["easymover"], "16.7 21.2 14.6": ["looketh"], "5.4 5.0 10.2": ["cytochromes"], "9.9 1.5 22.3": ["zucca"], "-4.5 0.3 4.1": ["phenelzine"], "10.8 0.9 9.5": ["caid"], "9.8 34.3 6.4": ["stryker"], "0.3 1.8 19.6": ["sze"], "4.9 11.2 17.8": ["balan"], "11.7 2.6 7.5": ["bipyridine"], "4.8 -3.1 13.7": ["wythnos"], "7.7 14.2 20.3": ["barko"], "7.7 4.5 1.2": ["nanosilicon"], "13.6 2.1 5.9": ["skinable"], "0.9 3.4 4.3": ["traitement"], "7.2 9.5 17.4": ["tipu"], "-0.6 2.3 6.2": ["myomas"], "-1.2 7.7 1.4": ["mikvaot"], "7.5 12.0 13.8": ["compulsives"], "10.7 3.8 14.2": ["aluminate"], "8.6 11.2 16.9": ["wheelnut"], "13.5 3.6 12.3": ["patronal"], "4.1 -3.6 0.6": ["unrefunded"], "13.1 8.5 14.6": ["lightful"], "11.6 13.7 8.7": ["butnot"], "12.0 24.4 22.7": ["strongyles"], "-3.6 4.1 10.9": ["evented"], "4.8 -3.2 13.0": ["nobile"], "17.9 27.7 4.2": ["guardposts"], "4.7 15.8 7.9": ["memogate"], "7.2 17.8 9.3": ["junkball"], "9.9 6.6 22.6": ["deerhound"], "11.5 5.3 5.8": ["radiactive"], "16.2 8.7 17.0": ["ticke"], "1.3 9.9 14.4": ["rosario"], "20.5 1.4 15.2": ["unbrushed"], "10.8 20.8 9.5": ["dangeorus"], "16.3 15.6 17.1": ["binnacles"], "5.7 5.2 3.3": ["orby"], "14.7 3.3 15.3": ["aahhs"], "1.2 -2.1 13.5": ["kasalukuyang"], "-4.1 -6.9 15.0": ["peabody"], "8.4 9.2 17.0": ["aversely"], "10.6 8.3 15.2": ["toros"], "5.8 22.2 11.9": ["pardoner"], "0.4 5.0 3.4": ["beginnen"], "1.4 3.0 3.4": ["anteriores"], "5.7 -4.6 2.4": ["nced"], "11.0 7.9 19.4": ["anagama"], "0.8 7.9 11.0": ["likha"], "18.6 13.1 4.8": ["phantastic"], "11.1 7.3 9.2": ["vitalised"], "1.1 3.8 8.6": ["sram"], "7.8 15.2 16.5": ["whaaaa"], "15.6 24.1 4.6": ["sonofagun"], "5.9 9.5 4.3": ["trabajos"], "13.6 -7.2 2.9": ["arkets"], "7.5 1.9 5.8": ["italien"], "6.6 9.6 7.2": ["turbinates"], "-1.1 2.6 2.5": ["patni"], "10.1 7.2 18.6": ["luo"], "3.8 8.6 6.8": ["reestimates"], "-8.3 -1.4 4.1": ["psychometrically"], "6.6 12.8 22.2": ["cornhusker"], "0.9 -1.5 1.1": ["diene"], "-3.0 8.0 9.7": ["querido"], "5.8 8.1 6.0": ["phenylene"], "2.7 18.7 -3.2": ["calliber"], "13.4 14.8 22.6": ["chemosynthesis"], "-2.9 -2.2 1.6": ["rary"], "5.8 -2.6 11.6": ["cuidado"], "12.9 7.8 4.4": ["lfl"], "1.7 7.9 11.1": ["tib"], "9.4 8.2 21.5": ["pacificus"], "4.7 13.4 1.6": ["gyrase"], "1.6 21.3 7.5": ["spacelift"], "-1.8 1.7 15.4": ["magkaroon"], "10.7 6.5 15.9": ["forreal"], "12.5 3.6 -1.7": ["codetermination"], "3.0 9.7 0.7": ["winwin"], "2.4 -3.1 3.4": ["xsp"], "10.3 9.2 6.2": ["illionaire"], "5.7 3.6 12.1": ["vus"], "17.4 3.6 26.6": ["nikau"], "2.6 -0.3 4.8": ["kathmandu"], "17.0 10.0 17.8": ["zowie"], "0.6 6.0 16.2": ["mahilig"], "10.8 10.9 22.1": ["unwiped"], "1.7 4.0 -7.6": ["cerebrations"], "1.2 18.5 11.4": ["ghters"], "11.3 7.9 21.7": ["deerstalkers"], "3.9 1.4 7.7": ["apcalis"], "1.0 -1.1 3.3": ["vance"], "3.5 -5.4 4.7": ["discontinuances"], "-2.7 18.0 7.4": ["ihsan"], "4.9 11.5 9.9": ["visuomotor"], "16.3 8.4 31.0": ["rufa"], "13.4 6.2 11.8": ["practicies"], "5.1 12.7 12.9": ["karoonga"], "2.1 8.3 8.8": ["hsiao"], "-5.0 6.2 11.0": ["erev"], "23.5 12.3 15.9": ["ceratopsian"], "6.7 -4.6 -3.3": ["socialresponsibility"], "11.0 3.1 7.7": ["nonfossil"], "10.4 2.7 13.7": ["lisbon"], "12.0 14.6 21.5": ["birdfeeding"], "0.2 -1.3 7.2": ["dickite"], "3.6 11.4 12.0": ["phreatic"], "-3.9 3.8 -8.5": ["ndependent"], "10.3 21.1 8.1": ["onmouseover"], "-4.8 -3.0 -2.5": ["souscripteurs"], "-6.2 2.9 7.6": ["anovulatory"], "10.6 16.6 15.0": ["orderers"], "4.2 12.0 9.4": ["highpass"], "-2.4 6.2 14.0": ["nondistressed"], "0.0 17.1 0.8": ["tularensis"], "9.2 -7.0 7.5": ["edp"], "4.9 2.9 13.7": ["ocasiones"], "17.6 13.0 28.5": ["chinaberry"], "-1.0 -0.8 11.6": ["maand"], "7.0 14.4 5.8": ["obsenity"], "-1.8 10.1 14.2": ["spinaround"], "10.5 9.0 8.1": ["redes"], "7.4 12.4 19.6": ["ectothermic"], "6.9 0.8 12.3": ["bandgala"], "10.1 6.0 21.3": ["lekvar"], "4.3 12.9 10.7": ["kalaripayattu"], "7.7 11.1 11.6": ["nyay"], "11.4 16.2 7.7": ["industralised"], "17.6 13.7 20.4": ["menhir"], "13.2 15.0 3.0": ["torridly"], "4.8 3.1 13.0": ["lactational"], "6.5 14.4 28.0": ["unboiled"], "12.5 0.7 -3.2": ["esmertec"], "26.2 8.7 43.8": ["longnose"], "7.8 8.6 15.9": ["boardsailor"], "15.1 1.4 24.5": ["especies"], "4.7 3.4 14.0": ["hakbang"], "-3.1 -1.1 10.4": ["activi"], "7.4 10.1 8.1": ["tente"], "13.6 4.6 5.9": ["boltless"], "0.8 -0.4 18.2": ["craftpersons"], "4.2 7.5 28.7": ["shami"], "0.8 -2.6 4.2": ["enero"], "-3.1 5.5 7.2": ["acromioclavicular"], "6.9 2.9 14.1": ["cuentas"], "13.6 25.6 8.4": ["apocolyptic"], "-3.4 13.2 -6.3": ["influ"], "4.5 4.6 1.3": ["simplement"], "12.6 10.1 23.2": ["tasy"], "13.5 20.2 4.6": ["essentialness"], "-1.2 -3.8 16.4": ["samesex"], "0.7 12.5 23.0": ["tungro"], "-4.6 5.7 10.8": ["truncal"], "15.3 5.0 15.3": ["fuls"], "3.6 6.1 13.0": ["nandun"], "9.1 5.3 18.6": ["tappy"], "11.2 -4.2 10.4": ["azioni"], "-2.2 -1.4 2.3": ["shinkin"], "8.8 1.6 29.5": ["platanos"], "8.5 -8.8 2.2": ["servizio"], "11.9 3.9 47.7": ["blacknose"], "-4.1 12.1 12.7": ["kegel"], "0.5 -2.3 15.0": ["kalusugan"], "10.5 4.7 31.2": ["orfe"], "0.6 3.3 8.9": ["opportu"], "13.3 7.5 18.7": ["calidad"], "14.1 2.7 19.1": ["trappist"], "1.1 7.9 4.6": ["uence"], "-5.9 11.3 8.1": ["beis"], "1.5 2.8 4.6": ["hyperosmolar"], "4.7 2.4 8.4": ["organis"], "12.5 0.7 22.1": ["piel"], "5.1 16.4 10.9": ["wouldas"], "6.5 11.3 9.7": ["scintillometers"], "17.1 8.7 16.8": ["cenbanks"], "12.0 5.1 1.6": ["dynabook"], "3.5 4.7 7.9": ["vermis"], "2.8 3.2 -0.8": ["coxsackie"], "2.6 7.3 14.8": ["socha"], "10.0 11.8 15.0": ["shiest"], "-2.5 8.6 13.5": ["dekhte"], "7.2 -0.9 33.1": ["limone"], "2.3 0.9 9.9": ["hexose"], "16.9 16.2 16.2": ["shoulderblades"], "2.7 4.6 5.2": ["diverses"], "9.0 -0.5 3.2": ["inh"], "0.7 15.6 15.1": ["sturmtruppen"], "-3.4 -2.6 9.7": ["lington"], "19.5 -4.5 -5.5": ["uropean"], "13.6 -3.2 22.2": ["harakeke"], "1.7 5.2 14.7": ["pancreata"], "11.0 7.6 19.9": ["geminata"], "-7.0 -0.8 0.3": ["nors"], "4.6 8.0 11.8": ["liftime"], "-1.5 5.2 6.7": ["oise"], "25.2 18.5 22.9": ["piglike"], "-0.2 10.3 8.8": ["arboviral"], "8.0 12.7 15.7": ["hablando"], "3.5 13.4 9.6": ["deinterlacer"], "22.2 9.2 25.1": ["manakin"], "16.7 5.0 2.5": ["cogenerating"], "5.6 8.5 9.1": ["gharar"], "7.5 10.5 5.9": ["vasovagal"], "1.0 9.1 1.6": ["unwedded"], "-7.1 -3.9 6.6": ["scl"], "15.3 -3.0 12.0": ["womenintechnology"], "9.1 26.4 0.9": ["unbudging"], "11.0 2.1 21.3": ["ohe"], "-2.8 -2.3 4.3": ["zhuh"], "-4.8 -0.3 9.2": ["ghan"], "6.3 -2.1 1.1": ["firmus"], "13.0 2.8 18.1": ["pinnata"], "9.8 -4.4 5.7": ["creare"], "6.2 -4.5 19.7": ["talu"], "7.2 -2.6 7.1": ["mpl"], "10.2 3.6 21.5": ["hirta"], "-2.5 5.1 7.5": ["degranulation"], "-0.5 32.0 8.9": ["templars"], "-2.8 19.7 3.1": ["perjure"], "8.9 29.4 7.8": ["neofascists"], "11.0 8.1 10.5": ["arpanet"], "5.5 -0.9 7.1": ["vaquilla"], "2.0 16.3 12.1": ["bursal"], "8.3 3.0 5.9": ["sealless"], "7.8 16.4 9.0": ["emember"], "5.1 6.6 -0.5": ["harman"], "4.5 8.3 5.7": ["multitargeted"], "3.2 19.1 6.5": ["ountries"], "12.0 10.4 9.2": ["remanent"], "-1.8 -2.9 1.2": ["agement"], "9.5 6.6 25.4": ["xie"], "2.9 15.3 17.3": ["sandhog"], "5.6 12.5 14.0": ["ciara"], "4.0 8.2 7.3": ["carloading"], "8.1 -0.8 -1.3": ["generat"], "-6.7 14.5 15.6": ["microprudential"], "3.2 7.7 0.5": ["jurisconsult"], "-7.0 2.5 4.1": ["atneed"], "3.6 18.0 8.1": ["sieg"], "-1.6 2.2 1.2": ["vxds"], "6.3 -5.8 13.6": ["artstream"], "7.9 11.0 7.5": ["lecteurs"], "7.8 12.2 9.6": ["kutta"], "16.9 10.1 11.7": ["tippin"], "5.5 8.0 7.6": ["obtener"], "-3.0 5.6 2.0": ["metastic"], "0.3 11.1 15.6": ["locksport"], "15.8 22.9 14.1": ["vampaneze"], "-0.6 -3.3 11.3": ["atleta"], "11.2 3.9 3.9": ["racesuit"], "15.0 0.0 10.9": ["mally"], "4.1 6.2 11.0": ["envoi"], "14.7 1.3 3.3": ["feasibilty"], "3.3 5.8 5.5": ["hepato"], "-1.1 -3.5 10.6": ["sopra"], "-0.6 0.6 5.3": ["exprienced"], "1.9 1.0 15.0": ["shien"], "0.6 8.6 4.1": ["noninjured"], "28.4 0.2 12.7": ["megasized"], "-1.8 1.8 4.0": ["unionisable"], "7.5 19.1 9.5": ["lifemate"], "2.7 4.8 11.4": ["torsionally"], "3.4 -2.1 13.4": ["ysbyty"], "7.5 3.0 18.6": ["ketum"], "5.7 12.6 12.3": ["lookee"], "23.4 12.1 20.7": ["greeen"], "9.4 13.7 16.2": ["rattier"], "-2.6 -0.3 5.5": ["luhn"], "-1.5 -1.8 4.0": ["sacrocolpopexy"], "13.1 7.8 21.0": ["oris"], "8.6 8.5 11.5": ["unidad"], "3.0 3.2 15.1": ["ollege"], "8.9 12.0 8.5": ["mosphere"], "3.0 9.3 15.5": ["pulitiko"], "6.0 7.5 19.6": ["moley"], "3.9 -4.0 18.6": ["kwok"], "4.4 19.2 10.5": ["seismogenic"], "7.9 -0.3 24.4": ["kumpanya"], "11.8 -6.2 8.1": ["supporto"], "-2.2 5.4 4.5": ["antithyroid"], "5.6 10.8 13.4": ["ufn"], "15.8 13.2 26.4": ["allergics"], "3.3 -8.4 3.3": ["qualif"], "12.6 10.2 14.6": ["stea"], "-1.8 14.8 -1.1": ["missio"], "2.8 14.9 28.4": ["habagat"], "-0.3 2.4 5.9": ["neurotoxicology"], "1.3 6.0 5.6": ["endometrioid"], "8.6 0.6 16.6": ["tante"], "-3.2 0.9 14.2": ["makukuha"], "-1.6 2.6 4.7": ["adamantane"], "1.6 9.8 -0.9": ["oncolytics"], "1.5 -5.8 8.1": ["swingline"], "1.3 8.2 5.7": ["reciver"], "14.5 1.5 19.1": ["jerkins"], "6.2 3.4 7.2": ["retraite"], "9.0 -8.4 19.9": ["kway"], "2.0 20.8 4.6": ["irreconciliable"], "7.2 12.9 17.0": ["lupeol"], "11.7 -1.2 30.2": ["merah"], "13.9 8.7 25.4": ["kakina"], "6.9 5.1 18.4": ["neto"], "3.4 -0.3 5.2": ["restor"], "0.6 9.5 11.0": ["cytidine"], "7.0 5.2 14.4": ["hori"], "0.6 0.2 0.2": ["rubel"], "1.6 -0.1 -0.2": ["carboxypeptidase"], "6.8 8.9 27.0": ["longarm"], "-1.1 -4.6 4.6": ["princi"], "9.7 21.5 10.8": ["formiddable"], "2.9 5.6 4.8": ["osteoma"], "14.2 1.4 13.3": ["inox"], "15.0 10.8 11.2": ["nanocage"], "3.8 4.3 6.2": ["unsedated"], "1.1 2.7 8.6": ["tetrathiomolybdate"], "-5.6 -7.2 6.0": ["pentose"], "16.9 -3.1 -1.3": ["newsbriefs"], "11.6 4.1 23.7": ["girthed"], "18.8 19.5 10.5": ["moanings"], "4.2 17.3 10.3": ["berkelium"], "9.8 2.3 18.0": ["noncaffeinated"], "-0.6 0.1 -2.0": ["dential"], "1.0 2.2 3.0": ["classifica"], "2.5 10.6 14.8": ["atra"], "-0.0 16.6 6.4": ["partis"], "9.2 -1.2 10.4": ["polycystic"], "5.2 13.3 16.6": ["steersmen"], "4.5 14.2 6.2": ["absolument"], "4.2 32.9 6.9": ["emplacers"], "22.1 10.4 14.0": ["agogo"], "3.0 12.0 5.1": ["faxless"], "10.8 -0.6 19.5": ["dockhand"], "-1.7 -9.7 4.2": ["yot"], "-1.5 -4.0 1.7": ["prepar"], "-10.4 -3.2 9.3": ["restrizioni"], "10.7 16.6 12.5": ["comput"], "3.1 30.8 4.4": ["discourtesies"], "2.1 11.0 12.8": ["upthrown"], "3.9 3.2 8.5": ["kieku"], "9.6 12.2 -1.8": ["serialisations"], "6.8 14.3 14.1": ["patang"], "3.4 19.1 6.9": ["pistoleiros"], "10.7 4.6 0.8": ["fanfics"], "-0.5 28.8 2.2": ["substitutionary"], "5.8 0.0 14.7": ["dermopathy"], "9.4 10.5 11.7": ["jimi"], "6.1 22.1 10.0": ["denotative"], "4.6 6.0 10.2": ["commencer"], "10.2 10.9 8.6": ["tching"], "5.9 7.5 15.0": ["skiathlon"], "-3.3 10.6 2.7": ["preambular"], "0.8 9.0 6.2": ["commissure"], "-2.8 4.3 3.9": ["tence"], "15.0 9.9 10.5": ["manouche"], "3.6 2.0 13.5": ["gonadotrophin"], "-6.8 7.6 1.2": ["sunat"], "9.5 6.9 1.6": ["widepsread"], "17.1 5.6 11.7": ["dooing"], "6.8 8.1 16.1": ["ulat"], "15.7 0.1 30.9": ["mikan"], "2.5 -4.3 8.1": ["monoethanolamine"], "0.5 2.9 3.6": ["misrecorded"], "8.6 16.8 7.1": ["photostreams"], "-12.0 0.8 2.8": ["iously"], "4.5 0.5 -1.0": ["igned"], "3.4 2.0 22.2": ["juncea"], "-2.1 9.1 -2.4": ["geddon"], "4.8 1.6 8.7": ["sizz"], "2.9 2.1 5.1": ["myotomy"], "8.3 1.1 19.7": ["acidifiers"], "3.6 6.2 10.2": ["shukla"], "21.0 7.5 17.8": ["sleekit"], "13.9 2.5 48.9": ["oreganata"], "25.8 8.8 15.1": ["silverleaf"], "23.1 11.1 28.9": ["demoiselle"], "4.2 5.2 6.3": ["folgenden"], "9.1 -3.6 9.5": ["lapband"], "-0.4 12.4 5.5": ["bindable"], "11.9 0.8 24.4": ["panne"], "-7.6 16.0 1.4": ["temperedness"], "1.8 6.1 17.1": ["vulputate"], "0.1 -5.3 -4.1": ["endorectal"], "0.9 13.1 7.1": ["exotropia"], "-4.5 28.7 -1.2": ["bounden"], "5.1 -14.5 6.3": ["ucation"], "10.8 16.6 11.4": ["moyes"], "12.4 -5.7 1.1": ["capitalmarkets"], "8.7 25.4 10.7": ["partyism"], "8.8 17.7 2.4": ["missionized"], "0.8 8.3 11.1": ["heureux"], "13.6 8.8 26.8": ["chhole"], "2.9 -0.9 2.4": ["priate"], "-0.7 3.6 5.7": ["pratiques"], "14.0 5.3 5.2": ["phasor"], "3.9 6.6 7.4": ["ege"], "-4.8 4.7 4.4": ["enterococcal"], "27.2 24.2 25.9": ["lightnin"], "6.3 8.1 14.5": ["mynd"], "2.9 10.3 9.4": ["labrums"], "-2.5 -2.5 4.4": ["hool"], "5.6 16.9 19.5": ["monomorphic"], "19.1 14.2 27.0": ["puddy"], "-2.1 13.3 19.5": ["nandiyan"], "2.7 16.1 26.5": ["amihan"], "11.5 9.8 12.2": ["orientational"], "0.9 8.5 -2.3": ["statem"], "7.4 7.0 2.1": ["bookazines"], "8.1 12.3 12.6": ["holemaking"], "10.0 19.5 1.2": ["gundas"], "12.8 12.0 13.6": ["firewagon"], "4.2 0.9 32.9": ["teow"], "11.3 5.9 4.4": ["ctrlcenter"], "3.0 22.5 6.4": ["techically"], "1.3 22.3 10.1": ["unnegotiable"], "5.4 -4.2 2.2": ["fixedrate"], "4.8 6.3 10.8": ["tweendeckers"], "6.8 8.3 11.7": ["rican"], "5.2 10.3 9.1": ["hittting"], "10.6 5.3 19.9": ["brandt"], "-3.2 16.4 14.0": ["neutrophilic"], "6.7 11.3 25.1": ["mande"], "11.4 9.3 9.8": ["mitras"], "20.2 8.6 31.4": ["pipevine"], "12.8 10.5 15.0": ["caras"], "13.2 17.8 12.3": ["waker"], "21.5 16.9 24.3": ["midocean"], "4.7 -4.0 -4.6": ["betaworks"], "6.6 15.1 10.2": ["foulers"], "-0.2 6.9 13.0": ["avium"], "-5.1 10.4 11.5": ["lieux"], "9.1 2.7 -4.3": ["transfert"], "3.9 11.2 0.9": ["othing"], "17.8 3.4 25.9": ["oxpecker"], "5.2 6.0 7.4": ["talkcast"], "3.5 11.5 13.3": ["bitties"], "2.2 9.2 11.6": ["translationally"], "-6.5 0.3 -1.2": ["pyridyl"], "-11.9 3.4 3.8": ["administra"], "2.2 -4.3 3.8": ["terfenadine"], "18.1 4.0 12.5": ["anticholesterol"], "8.4 7.3 14.9": ["absinth"], "17.3 19.4 20.7": ["puppydog"], "4.0 -5.2 11.4": ["disponibili"], "2.5 21.1 13.5": ["defiers"], "4.2 6.9 11.8": ["circumcises"], "3.7 -3.0 1.0": ["intragastric"], "13.7 19.1 25.6": ["axils"], "6.5 6.1 28.6": ["prik"], "-1.1 11.0 19.3": ["nasabi"], "10.2 9.6 2.2": ["nanosurgery"], "0.5 3.4 9.4": ["maglaro"], "15.4 11.4 9.5": ["valse"], "0.2 4.2 4.6": ["aio"], "11.3 12.4 0.2": ["stromuhr"], "6.6 8.1 14.5": ["sjr"], "6.2 8.9 5.3": ["groupons"], "3.1 -3.5 10.0": ["modello"], "11.0 -1.5 13.1": ["plataforma"], "8.9 10.7 7.4": ["betchas"], "1.6 22.4 8.3": ["disrepected"], "20.8 2.6 13.3": ["exxon"], "-3.8 -8.4 -5.1": ["ases"], "0.1 11.6 1.4": ["pradeep"], "12.7 20.7 14.7": ["lectularius"], "-5.3 -10.9 7.1": ["llen"], "16.0 5.3 5.0": ["gebruik"], "-7.4 9.3 1.2": ["controverting"], "4.4 7.9 14.3": ["lightener"], "15.3 -0.4 10.5": ["parque"], "2.7 8.9 2.8": ["porphyric"], "-8.0 7.4 3.0": ["gonococcal"], "1.9 11.8 -0.5": ["officio"], "-7.0 6.4 6.8": ["chronologic"], "4.2 3.4 7.0": ["polybrominated"], "5.2 16.2 15.1": ["sheperd"], "7.6 5.7 9.1": ["pean"], "10.9 4.1 -4.6": ["mtc"], "21.2 -4.1 7.9": ["npat"], "4.0 7.9 15.2": ["daro"], "14.2 23.2 16.1": ["prowlings"], "9.2 -4.6 2.7": ["parfums"], "10.9 4.7 15.9": ["controles"], "7.8 17.8 29.1": ["shelduck"], "7.4 3.7 7.4": ["artparis"], "9.3 -0.0 5.1": ["arpu"], "2.8 -3.9 -2.7": ["hydrodesulfurization"], "-2.9 4.8 10.6": ["layo"], "4.3 11.0 20.4": ["bilis"], "3.5 4.5 4.2": ["unseren"], "7.3 7.9 2.3": ["mitgeteilt"], "-0.7 12.7 11.1": ["coparenting"], "1.6 -1.9 6.4": ["hepa"], "4.3 1.2 0.1": ["valvuloplasty"], "2.1 3.4 8.3": ["chatterjee"], "16.0 11.8 17.4": ["glasswool"], "15.7 5.9 10.4": ["perts"], "11.0 -4.4 -0.8": ["rahn"], "9.7 3.7 8.8": ["levigating"], "8.6 1.3 7.6": ["antigua"], "0.8 -4.3 4.3": ["milioni"], "15.2 9.3 -0.8": ["doly"], "2.1 11.9 4.6": ["chemopotentiator"], "-0.5 2.6 8.0": ["motorela"], "20.1 9.8 21.1": ["rolltop"], "8.5 13.5 34.9": ["gallinule"], "10.1 11.0 15.1": ["septums"], "8.6 10.3 19.1": ["biel"], "21.1 7.4 13.2": ["squeakiest"], "0.3 7.7 11.9": ["buo"], "19.0 3.3 2.8": ["webbook"], "-2.2 7.3 -1.6": ["whethere"], "5.5 5.6 8.9": ["phakic"], "7.0 -0.5 -0.7": ["ammeters"], "16.4 8.1 15.4": ["mullioned"], "5.5 7.7 9.1": ["oppty"], "-7.2 -5.4 -4.6": ["bmc"], "23.4 10.1 47.0": ["sweetlip"], "11.3 7.3 23.7": ["pagne"], "9.5 4.0 8.3": ["blod"], "-9.2 0.9 6.5": ["showrunning"], "3.6 13.6 14.2": ["subclauses"], "4.0 -5.5 -0.0": ["telerik"], "-8.0 5.9 9.2": ["syndromal"], "9.1 14.9 11.1": ["recriminalize"], "19.3 10.8 1.5": ["multistoreyed"], "-9.9 3.8 15.0": ["magkakaroon"], "4.7 10.3 13.4": ["viet"], "-1.3 6.1 18.9": ["lalawigan"], "23.0 6.6 30.9": ["wharfside"], "17.1 8.2 11.6": ["bundy"], "11.3 -0.1 5.9": ["nonfusion"], "10.3 -0.5 27.3": ["tavola"], "13.3 5.0 10.3": ["sweatpant"], "2.4 0.2 7.1": ["tsx"], "-0.2 3.9 14.8": ["bibigyan"], "16.9 21.9 11.0": ["rulez"], "12.0 9.5 10.9": ["proyectos"], "1.4 7.0 19.3": ["ngwana"], "-6.6 10.1 2.6": ["nondebtor"], "1.6 -1.2 5.7": ["huber"], "1.0 13.9 16.2": ["gair"], "1.3 8.6 17.4": ["uninsurables"], "1.0 23.4 2.7": ["militarylike"], "13.2 11.6 5.1": ["unmerged"], "11.8 7.1 17.0": ["clenchingly"], "27.3 -0.9 -0.5": ["milti"], "14.1 7.7 3.2": ["mobilis"], "8.9 16.8 28.2": ["flippity"], "17.3 8.9 24.1": ["brillo"], "2.0 6.7 8.9": ["samahan"], "11.8 10.9 20.1": ["moldboard"], "10.5 16.7 6.6": ["suppresser"], "8.2 6.7 30.8": ["lemak"], "4.7 5.4 11.8": ["multiresistant"], "7.5 11.2 11.6": ["murmer"], "-2.0 3.6 9.6": ["dysbindin"], "4.7 0.1 9.0": ["serialiser"], "2.3 4.0 14.1": ["darating"], "12.4 1.8 10.9": ["nanochips"], "0.7 12.0 11.6": ["neurotropic"], "0.6 11.8 0.3": ["offizielle"], "-2.4 3.2 8.7": ["valima"], "-10.2 17.0 -3.6": ["candidated"], "10.0 20.2 19.0": ["actu"], "6.6 7.6 7.0": ["iridix"], "7.7 -3.5 3.8": ["archivos"], "9.0 2.2 8.2": ["avante"], "5.0 7.4 10.1": ["keratoconjunctivitis"], "-4.6 7.3 3.6": ["accep"], "3.0 15.3 9.1": ["nonshooting"], "15.4 6.2 18.5": ["rilly"], "16.4 15.0 25.4": ["backstays"], "7.5 -3.2 8.5": ["duffy"], "-3.1 7.7 8.1": ["kla"], "6.6 -4.1 5.8": ["photoconductors"], "-3.7 11.5 6.1": ["constiuency"], "10.7 9.0 25.4": ["gallego"], "6.9 3.8 8.6": ["gillard"], "3.1 -2.1 2.4": ["istory"], "4.0 5.9 18.0": ["bonheur"], "5.6 2.8 12.4": ["arabinogalactan"], "13.4 14.7 15.8": ["undermounted"], "5.1 9.4 7.4": ["polycomb"], "-1.3 12.0 7.0": ["ithin"], "9.8 7.4 14.5": ["centrifugally"], "1.0 8.5 8.5": ["kasih"], "3.5 2.0 11.1": ["edifoligide"], "4.8 20.4 3.6": ["strenously"], "28.4 -2.9 11.7": ["foodseller"], "-2.4 1.9 7.6": ["weatherwoman"], "6.8 16.1 8.4": ["shipwide"], "-4.3 4.6 0.3": ["decid"], "3.4 16.0 -1.6": ["undertreating"], "14.1 18.3 10.6": ["bigamously"], "-2.3 -1.0 1.4": ["qualit"], "22.4 8.4 -0.8": ["multibranded"], "11.5 42.7 9.9": ["geth"], "-6.2 -4.6 -3.6": ["ngel"], "-5.4 -2.8 5.3": ["norgestimate"], "10.4 -2.5 10.2": ["troffers"], "1.8 13.3 12.2": ["albitite"], "6.6 -0.6 2.6": ["serveurs"], "-0.3 14.9 5.0": ["sectionally"], "2.6 10.9 0.4": ["talibe"], "17.0 7.2 32.2": ["crowder"], "14.9 -0.5 36.5": ["formaggi"], "20.6 6.6 15.1": ["brazo"], "11.7 7.9 10.8": ["perder"], "21.0 13.5 39.5": ["pteropod"], "4.2 31.2 -5.0": ["weaponeer"], "8.6 4.5 18.8": ["coffinettes"], "25.6 15.2 31.7": ["swordlike"], "20.2 6.5 35.3": ["cheeseless"], "3.3 -0.3 8.0": ["retrait"], "0.9 13.3 12.8": ["kasamahan"], "-2.5 16.9 3.5": ["llah"], "2.5 7.6 16.2": ["insidente"], "5.0 -3.3 10.0": ["unig"], "-4.0 -1.2 1.2": ["cholecystectomies"], "2.9 -1.2 3.6": ["pollbook"], "4.9 3.9 7.1": ["rsquo"], "5.2 5.0 15.7": ["maun"], "15.0 17.6 10.8": ["unspontaneous"], "2.9 8.1 15.5": ["buwis"], "5.0 3.0 6.2": ["subkeys"], "-2.7 1.0 2.9": ["empha"], "3.0 12.4 6.9": ["multibit"], "5.2 15.1 8.0": ["verwendet"], "6.8 5.2 5.2": ["unitrust"], "14.4 9.8 29.1": ["tabebuia"], "3.8 10.8 9.1": ["difficul"], "9.8 0.5 24.0": ["niloticus"], "6.6 3.9 20.6": ["taua"], "3.6 6.7 5.4": ["onight"], "-2.1 1.3 31.0": ["kerabu"], "1.2 -0.5 11.2": ["clienti"], "-3.9 17.3 0.8": ["attributional"], "-2.0 -8.6 11.1": ["orded"], "4.1 11.3 4.4": ["twstephens"], "3.5 7.0 22.9": ["imong"], "7.0 17.8 1.7": ["erhaps"], "6.0 1.4 1.3": ["osition"], "-1.2 9.9 14.9": ["epigallocatechin"], "-3.4 12.7 11.1": ["nonabusive"], "21.5 -2.2 -4.2": ["titsup"], "8.8 12.9 11.7": ["lighteners"], "8.4 14.1 -0.1": ["toyi"], "8.8 -4.6 17.1": ["propiedad"], "10.5 2.3 6.0": ["esposa"], "6.9 -7.2 7.1": ["twoand"], "-13.5 -1.0 6.4": ["cident"], "10.8 7.6 16.6": ["exurbanites"], "4.0 4.1 2.2": ["resynchronizes"], "3.7 4.3 40.0": ["almandine"], "19.5 5.2 8.0": ["belchers"], "1.4 7.9 5.3": ["mismos", "ffffo"], "10.0 7.3 3.6": ["ivied"], "0.3 8.0 9.4": ["aminotransferases"], "1.6 10.9 11.0": ["kaisi"], "0.2 6.2 15.0": ["umpisa"], "5.2 12.1 21.0": ["cullen"], "3.7 5.8 21.1": ["chitra"], "15.7 11.5 34.8": ["frigatebird"], "1.5 17.5 7.4": ["jaati"], "8.2 6.7 4.2": ["aantal"], "3.7 5.6 20.8": ["refsoyoil"], "8.6 4.5 16.2": ["sicrhau"], "0.3 4.1 2.8": ["tracting"], "0.5 -5.1 -0.1": ["professionnels"], "9.1 17.1 24.8": ["unbanded"], "5.0 19.7 22.7": ["irruptive"], "1.1 4.4 23.2": ["syruping"], "10.6 7.9 19.8": ["viento"], "9.6 7.7 14.6": ["kuthu"], "20.9 8.1 20.0": ["saj"], "-0.0 6.5 5.1": ["arthrography"], "9.0 18.9 23.9": ["canebrakes"], "10.0 16.0 4.2": ["jesture"], "-3.5 4.0 5.5": ["cortico"], "15.2 5.4 19.9": ["puestos"], "0.6 26.9 4.3": ["tollerance"], "-0.0 1.7 13.5": ["empleyado"], "13.4 6.0 18.7": ["waxless"], "22.1 6.8 21.1": ["nutlike"], "8.6 11.0 12.1": ["nop"], "1.2 9.5 10.3": ["merozoite"], "4.5 0.0 5.7": ["htp"], "11.5 6.0 9.6": ["mechanist"], "0.9 6.4 6.1": ["itive"], "-3.7 -4.1 12.4": ["irri"], "0.7 -1.9 -1.9": ["invol"], "0.1 10.1 2.2": ["escooter"], "1.1 -2.7 14.1": ["pareja"], "-2.6 -4.2 -1.4": ["cns"], "15.8 8.9 12.5": ["corde"], "7.1 3.2 7.5": ["organismo"], "9.3 9.8 2.1": ["rces"], "-0.6 1.6 -1.0": ["rgen"], "10.1 9.3 4.9": ["hailers"], "3.2 11.9 4.4": ["lectio"], "5.0 7.1 11.5": ["escrito"], "1.9 10.8 4.1": ["antitumoral"], "9.5 3.2 15.2": ["noncaloric"], "5.6 12.7 6.1": ["bevor"], "0.2 -4.5 -7.4": ["ophthamologist"], "-4.0 -0.3 7.6": ["lectura"], "10.6 2.8 15.5": ["dichloride"], "7.2 -3.3 2.1": ["lancement"], "12.4 2.2 29.9": ["muhly"], "20.0 2.7 23.9": ["linzer"], "14.3 15.2 19.3": ["improbables"], "-2.5 2.7 8.1": ["mjs"], "14.2 3.9 12.9": ["babygros"], "5.4 0.8 8.6": ["studless"], "-4.0 12.1 -0.6": ["vertebrobasilar"], "3.8 14.1 20.1": ["sethu"], "1.4 3.6 5.6": ["karina"], "-0.5 7.9 10.4": ["ubiquitinated"], "7.6 5.1 9.7": ["espacio"], "7.2 9.5 4.1": ["laurent"], "13.6 7.0 22.5": ["malodour"], "11.8 12.9 10.1": ["titolo"], "-8.8 0.3 2.9": ["inson"], "-3.1 1.5 10.2": ["odl"], "17.2 10.6 28.4": ["dillies"], "4.0 11.4 14.6": ["ciudadanos"], "21.6 1.9 18.9": ["playlands"], "13.1 13.1 12.5": ["gayly"], "5.4 8.3 15.1": ["greensboro"], "14.2 8.1 7.7": ["reductio"], "5.2 0.8 11.6": ["hsp"], "5.6 0.5 7.4": ["joueur"], "3.6 17.9 0.4": ["gujrat"], "-0.8 14.8 -0.5": ["embarras"], "-2.5 20.1 4.4": ["ghting"], "-1.9 -2.7 10.2": ["multiplexor"], "15.4 0.4 8.9": ["diferencia"], "8.1 10.4 9.7": ["recurse"], "18.6 3.4 10.0": ["browserless"], "10.4 9.1 19.7": ["nimbu"], "0.6 10.2 6.0": ["paath"], "4.4 8.8 7.7": ["frameshift"], "-2.2 3.4 -2.9": ["neurokinin"], "1.0 -0.1 3.6": ["tair"], "-2.1 24.3 6.7": ["derech"], "4.0 3.4 11.4": ["racine"], "2.1 6.1 15.7": ["daru"], "3.4 5.4 23.2": ["flos"], "6.9 -6.0 -2.9": ["ications"], "6.8 25.5 2.7": ["pacifically"], "-4.0 9.5 10.4": ["pakialam"], "6.4 1.6 9.6": ["archivo"], "4.8 8.2 3.8": ["infantis"], "15.7 4.4 23.3": ["ajo"], "17.1 2.9 9.0": ["woodcare"], "15.5 2.3 4.1": ["ultrasuccessful"], "6.5 9.5 26.2": ["sativus"], "-5.7 -3.1 5.6": ["prophy"], "20.7 8.2 20.6": ["boggers"], "1.0 6.8 9.7": ["representante"], "-2.4 8.0 7.4": ["nonsedating"], "10.8 9.4 10.3": ["grrrls"], "0.2 -2.0 6.0": ["segundos"], "-3.5 26.2 -4.2": ["atttacks"], "12.0 3.0 0.4": ["holter"], "2.3 5.6 11.9": ["floodprone"], "21.3 6.4 19.9": ["wainscoted"], "9.3 -8.1 25.2": ["deerskins"], "-2.1 7.7 4.1": ["vivah"], "10.1 22.7 11.5": ["antisocially"], "9.3 6.2 29.8": ["pesca"], "-7.5 3.2 9.4": ["gth"], "-6.2 4.8 11.7": ["nakikitang"], "2.7 21.9 -1.3": ["grievious"], "5.7 -0.5 10.4": ["electrogalvanized"], "5.2 20.7 14.2": ["forgetfully"], "12.7 12.9 6.3": ["automotively"], "4.4 4.8 17.2": ["shearings"], "6.8 5.5 13.6": ["genda"], "16.8 10.4 16.4": ["videophilia"], "-1.1 2.2 4.3": ["transmountain"], "-1.6 3.9 4.0": ["displinary"], "-0.5 4.4 6.4": ["dominio"], "7.6 8.3 9.9": ["ricardo"], "0.4 8.7 -0.8": ["modifiability"], "11.9 8.4 20.4": ["retractile"], "16.1 11.4 19.9": ["wrestlin"], "8.1 8.6 15.2": ["nepheline"], "14.7 12.2 19.2": ["jewelcrafting"], "13.8 11.1 8.7": ["sharpton"], "-3.0 2.1 18.1": ["nagkaroon"], "-13.0 0.7 1.5": ["hyperoxaluria"], "6.3 11.6 12.1": ["stretchout"], "0.3 -1.4 0.1": ["essor"], "5.2 8.1 8.7": ["cpf"], "14.1 8.2 3.5": ["osphere"], "12.2 5.4 11.8": ["coche"], "-1.6 3.6 14.0": ["childr"], "15.9 0.7 14.2": ["graphites"], "15.0 -6.8 4.9": ["breakrooms"], "2.2 8.3 13.8": ["menaquinone"], "18.4 7.4 31.6": ["podge"], "7.2 17.2 17.9": ["incognita"], "2.4 9.4 18.8": ["dentro"], "-2.8 -11.1 5.0": ["gwah"], "12.4 6.0 -1.7": ["iptelorg"], "12.4 12.1 12.7": ["iconish"], "4.7 5.6 9.3": ["pobres"], "7.0 -6.7 6.0": ["partici"], "12.8 9.6 17.0": ["terremoto"], "3.3 3.3 0.9": ["deuk"], "1.4 8.3 14.2": ["blebby"], "17.4 16.9 24.9": ["bathyscaph"], "0.2 8.5 10.3": ["pagal"], "5.9 -0.8 5.7": ["occas"], "15.9 12.2 2.4": ["eris"], "1.6 5.2 12.7": ["fected"], "17.8 14.0 27.1": ["bubblin"], "16.8 9.1 17.2": ["basters"], "5.1 15.1 8.3": ["gga"], "2.8 5.3 16.0": ["tumawag"], "10.1 14.2 21.4": ["facelock"], "-1.5 2.3 -0.3": ["detatchment"], "10.6 8.8 14.3": ["jointers"], "2.6 13.3 29.1": ["myrosinase"], "15.8 18.1 14.9": ["rethread"], "0.5 -0.1 0.5": ["winhec"], "4.5 2.8 6.2": ["leez"], "9.7 16.5 14.1": ["clutchest"], "15.7 -9.4 26.6": ["honeycrisp"], "-3.9 -3.4 1.1": ["embedder"], "-5.8 2.8 6.6": ["asplenia"], "11.0 7.1 35.7": ["blanquette"], "-2.2 -2.9 5.8": ["doxercalciferol"], "20.9 5.7 31.0": ["cuitlacoche"], "11.7 12.8 18.2": ["latite"], "2.7 -2.2 -2.5": ["initia"], "8.0 5.4 12.0": ["khim"], "0.3 3.1 6.0": ["chhoti"], "11.3 12.4 19.6": ["simms"], "6.0 10.1 23.4": ["sepulchres"], "15.2 -1.1 8.5": ["multispace"], "5.3 27.4 -0.5": ["destructionists"], "-5.0 11.3 1.3": ["islami"], "2.7 -4.8 2.0": ["vihn"], "-1.4 8.1 5.6": ["frontostriatal"], "4.8 0.2 7.9": ["tareas"], "17.2 5.9 7.6": ["spikeless"], "11.4 0.6 15.5": ["blonded"], "-10.2 8.1 0.4": ["neuromelanin"], "10.2 10.7 20.0": ["klang"], "4.4 17.0 10.4": ["peeta"], "5.6 4.1 13.5": ["dsc"], "14.7 19.0 17.3": ["furriness"], "4.0 22.0 5.3": ["smolderingly"], "8.6 9.6 0.6": ["howeve"], "10.9 2.4 14.6": ["fructooligosaccharides"], "13.5 11.5 15.8": ["shlumpy"], "6.9 17.4 12.3": ["whadda"], "3.7 3.8 14.2": ["peau"], "5.8 11.0 10.2": ["biswas"], "8.1 9.7 22.5": ["campestris"], "7.3 19.1 -3.5": ["lefist"], "-3.9 -4.9 -4.2": ["zuhl"], "14.3 5.9 33.1": ["downlake"], "9.3 1.4 4.5": ["storyed"], "5.0 12.6 9.4": ["degradative"], "9.8 11.7 17.5": ["liza"], "0.2 7.7 5.1": ["enteroviral"], "-1.8 -10.0 8.1": ["covery"], "8.0 3.6 14.3": ["symud"], "7.9 3.5 2.8": ["aktiviert"], "7.1 7.5 8.6": ["pantalla"], "-2.1 5.1 11.9": ["tanging"], "5.4 18.7 4.6": ["fretters"], "15.0 0.5 8.2": ["ergy"], "-0.7 9.0 2.2": ["labetuzumab"], "29.8 15.5 5.4": ["basf"], "-3.2 -12.2 5.8": ["rative"], "-0.2 2.3 6.0": ["rej"], "3.5 9.6 12.4": ["ullamcorper"], "2.9 5.9 4.9": ["dysgenesis"], "8.0 4.6 28.0": ["wholphin"], "8.7 6.5 8.1": ["albion"], "5.5 4.6 26.8": ["minyak"], "8.9 11.6 7.3": ["colorspace"], "-3.7 -1.9 3.4": ["nontoll"], "0.9 13.4 12.2": ["prepositional"], "15.8 0.7 -0.7": ["gagner"], "26.8 11.5 18.4": ["spokesclown"], "6.1 2.6 41.7": ["magret"], "5.5 8.7 10.6": ["postmistresses"], "3.7 -0.7 6.4": ["zhee"], "6.0 10.8 11.5": ["mutally"], "11.1 8.1 36.7": ["bonytail"], "4.7 7.1 8.7": ["astrophotographers"], "4.3 6.2 14.1": ["cancion"], "9.1 9.3 13.8": ["ratha"], "13.1 -1.2 1.4": ["variante"], "8.7 1.5 13.3": ["rowth"], "3.9 2.3 3.1": ["barbituate"], "-3.7 4.6 5.8": ["hyperinsulinism"], "7.2 8.5 20.5": ["langit"], "11.0 3.0 35.3": ["borlotti"], "1.4 3.4 -1.4": ["jfs"], "9.6 -2.7 -5.0": ["gesamten"], "-1.2 9.1 11.8": ["pananaw"], "13.7 3.0 8.8": ["semipermeable"], "10.8 17.6 16.6": ["whaaat"], "16.6 6.4 37.8": ["crucian"], "10.0 14.0 9.1": ["confianza"], "23.3 12.2 12.7": ["electrochromatic"], "-6.9 5.7 4.5": ["provin"], "-8.1 1.5 6.1": ["rday"], "6.6 1.0 2.3": ["analy"], "-0.7 3.5 15.2": ["nonreleasable"], "22.2 7.3 10.0": ["rulemaker"], "6.0 8.0 8.3": ["ught"], "4.9 7.5 7.0": ["lequel"], "20.0 11.5 19.5": ["crossbedding"], "1.6 7.9 -0.6": ["bilaterial"], "5.1 13.1 4.5": ["sarvajan"], "2.1 13.3 12.4": ["bup"], "3.8 8.6 9.1": ["decisi"], "1.6 1.3 1.6": ["chel"], "-0.8 3.7 2.1": ["evelyn"], "16.8 13.5 4.3": ["begginning"], "1.6 9.3 6.6": ["saria"], "12.1 8.1 17.0": ["bakfiets"], "7.5 12.9 19.2": ["melayu"], "11.7 8.4 25.4": ["lume"], "15.0 5.2 20.7": ["whistlin"], "13.4 1.3 20.2": ["oinked"], "18.0 3.4 12.5": ["squeakily"], "-1.1 16.2 8.8": ["rived"], "5.2 -2.3 13.1": ["lors"], "10.2 12.0 25.4": ["thung"], "1.9 -0.6 2.9": ["targetters"], "5.0 7.6 5.6": ["urther"], "1.4 -0.4 -1.6": ["inkset"], "8.6 0.1 11.3": ["axleshafts"], "2.6 8.7 15.4": ["erika"], "15.7 17.3 29.6": ["overexploit"], "8.9 8.7 13.8": ["mycosis"], "1.7 15.4 10.2": ["mistargeted"], "9.5 10.5 11.3": ["gustier"], "10.0 15.9 5.3": ["unabomber"], "11.8 15.5 14.8": ["goodnaturedly"], "5.9 16.4 14.8": ["pussed"], "0.7 4.2 4.5": ["tiuxetan"], "8.4 3.0 7.6": ["millimeterwave"], "2.8 8.4 9.9": ["revolucion"], "17.9 0.1 14.2": ["superficie"], "7.2 7.0 10.2": ["plica"], "20.1 1.0 39.4": ["rollatini"], "-4.2 6.1 11.6": ["dehydrogenases"], "12.0 3.4 14.3": ["facers"], "1.9 2.7 7.8": ["ganze"], "6.6 4.1 6.9": ["adesso"], "-4.9 4.9 10.7": ["aayegi"], "-4.1 12.7 7.9": ["wakil"], "-7.5 4.1 12.7": ["sabay"], "13.3 0.0 21.7": ["kumain"], "11.1 16.6 14.1": ["groggers"], "0.9 -2.3 -9.5": ["adua"], "7.0 -0.8 10.8": ["webseminars"], "1.1 2.5 16.5": ["biblioteca"], "-1.6 7.1 4.9": ["prils"], "4.6 0.8 1.1": ["fichiers"], "-2.6 21.5 -0.2": ["wasallam"], "-15.2 -2.7 -2.0": ["gations"], "-6.8 8.2 -2.8": ["vulvovaginal"], "1.0 0.6 0.6": ["registra"], "11.8 1.7 13.8": ["sedex"], "-0.2 12.8 6.6": ["conditio"], "7.2 6.7 0.5": ["germier"], "14.6 7.9 42.4": ["talaya"], "3.6 11.9 7.1": ["multibody"], "-3.3 0.1 13.5": ["pasok"], "6.8 1.4 15.4": ["humano"], "6.0 0.2 8.5": ["depen"], "-8.6 8.6 15.2": ["riverain"], "10.1 -5.8 10.8": ["multisegment"], "13.3 14.1 14.3": ["electrolyzing"], "14.4 8.6 16.6": ["bhoy"], "3.8 4.4 13.6": ["maaari"], "6.0 13.0 15.1": ["weirdy"], "2.2 -4.8 -0.9": ["occluders"], "7.2 4.5 -0.1": ["methanation"], "-0.0 5.1 17.9": ["pombe"], "10.1 1.5 3.0": ["llamadas"], "8.0 36.3 7.3": ["witchers"], "13.7 9.2 11.6": ["racily"], "17.8 11.4 19.0": ["driveside"], "7.6 8.0 9.7": ["luther"], "-2.1 4.8 8.1": ["pauline"], "19.3 2.9 0.2": ["dropboxes"], "2.9 14.4 11.0": ["surpris"], "4.7 8.1 11.9": ["microvessel"], "-1.2 8.1 5.8": ["fico"], "8.0 5.7 1.1": ["cephalometric"], "-6.1 3.1 5.7": ["asperger"], "2.2 9.5 4.1": ["paix"], "15.7 9.6 22.2": ["unchipped"], "18.0 -1.5 23.0": ["hoola"], "14.4 4.9 1.1": ["vaio"], "13.3 13.7 26.9": ["buttie"], "22.8 4.0 7.3": ["toystore"], "6.9 -5.0 2.8": ["bioorganic"], "-1.2 -5.7 1.6": ["soluzione"], "13.1 1.0 12.5": ["panky"], "1.1 -9.9 2.3": ["subcode"], "16.6 12.2 9.5": ["unarranged"], "4.6 13.4 7.5": ["patriate"], "3.8 1.7 8.1": ["polycystin"], "-0.3 27.1 9.8": ["hateth"], "19.3 14.9 18.1": ["doodly"], "7.8 10.2 10.7": ["sjm"], "6.4 4.1 2.7": ["secre"], "12.2 7.9 2.8": ["pygas"], "-0.5 8.4 15.2": ["dekhi"], "12.5 8.5 18.8": ["minny"], "-2.7 6.8 4.8": ["esterases"], "0.6 4.8 16.0": ["suspek"], "1.0 11.5 5.3": ["peine"], "-0.6 3.5 12.7": ["sulcal"], "2.4 10.1 12.1": ["abbr"], "-1.6 1.8 1.8": ["reportcard"], "3.8 7.5 3.0": ["conflicto"], "0.7 22.0 8.4": ["untrain"], "3.2 -1.1 14.7": ["foodstamp"], "0.7 2.5 -3.7": ["andarine"], "15.9 10.5 16.7": ["uncarbonated"], "5.7 -7.1 2.3": ["partenariat"], "15.3 5.3 12.3": ["commmodity"], "-3.5 14.2 9.4": ["hashem"], "3.5 11.1 11.1": ["exigences"], "8.3 9.4 4.2": ["santour"], "7.8 16.8 19.1": ["naturedly"], "9.3 7.8 26.9": ["springsnail"], "14.8 12.8 16.5": ["mees"], "6.3 2.9 2.3": ["deformational"], "10.5 8.3 18.1": ["gussa"], "4.4 -4.4 9.4": ["scheda"], "7.5 3.2 6.9": ["urday"], "6.8 15.6 21.3": ["serratus"], "6.1 3.7 36.8": ["iberico"], "-0.6 17.6 0.7": ["imprisonable"], "-2.6 5.4 6.7": ["naso"], "5.7 3.8 10.0": ["preaddressed"], "0.5 15.7 7.8": ["inurement"], "0.9 6.4 14.3": ["residente"], "-2.4 4.8 1.4": ["transimpedance"], "18.7 -2.9 10.1": ["methylnaphthalene"], "20.4 -3.0 0.8": ["aandelen"], "-4.2 1.4 9.0": ["basecoats"], "18.0 17.3 15.7": ["glary"], "8.6 3.6 14.8": ["newspa"], "5.2 2.5 11.1": ["impacto"], "-4.7 8.1 -2.1": ["psychosocially"], "8.1 12.6 7.7": ["failproof"], "0.1 9.4 3.9": ["nuncios"], "10.3 0.2 8.9": ["getready"], "-2.5 2.0 -7.5": ["cturing"], "10.4 3.3 28.2": ["lyonnaise"], "3.4 -0.2 3.0": ["ventes"], "11.2 0.3 20.6": ["leaveners"], "9.1 5.0 5.2": ["nontraded"], "4.4 11.9 15.7": ["duine"], "1.9 7.6 14.3": ["awan"], "-10.4 2.4 0.8": ["thrombocytosis"], "8.5 2.8 4.4": ["mello"], "2.8 6.4 10.9": ["assa"], "-1.8 1.9 0.0": ["hyperresponsiveness"], "15.0 10.4 14.3": ["judd"], "18.9 4.6 9.6": ["wafter"], "11.9 1.3 16.7": ["luen"], "-4.0 -4.1 7.3": ["duhl"], "5.7 8.4 11.7": ["doute"], "-4.4 1.8 13.9": ["manggagawa"], "3.9 22.3 10.3": ["kovils"], "2.3 3.3 3.8": ["agente"], "0.2 1.9 15.1": ["eileen"], "11.8 0.8 20.0": ["syne"], "9.9 -0.9 2.4": ["financement"], "1.6 3.9 21.7": ["lumaki"], "10.2 2.2 2.3": ["parfaitement"], "4.8 7.1 3.5": ["imani"], "14.7 8.5 7.6": ["ambooba"], "5.7 -2.7 -2.3": ["consequentials"], "10.8 1.5 21.5": ["barelegged"], "10.3 8.6 12.8": ["metabase"], "14.8 20.3 35.4": ["shortnose"], "0.4 2.7 9.5": ["balitang"], "12.1 -4.8 15.4": ["handknitted"], "9.5 14.0 16.4": ["shab"], "13.5 15.7 8.1": ["savate"], "20.2 3.3 10.7": ["scootin"], "9.9 19.6 3.9": ["teamplayer"], "13.6 2.2 12.0": ["fresnel"], "-1.4 0.7 8.8": ["remarketings"], "1.6 8.1 11.9": ["neurofilament"], "0.4 20.0 16.4": ["nonhunter"], "2.8 6.2 11.7": ["paperworkers"], "16.8 2.7 9.7": ["maharatna"], "14.7 7.3 30.4": ["heelsplitter"], "-1.1 -5.4 4.3": ["tfi"], "9.8 -12.7 6.4": ["nium"], "10.0 -2.6 11.4": ["frontmonth"], "4.7 7.9 13.6": ["dawk"], "6.5 10.9 19.9": ["nasud"], "5.8 6.7 7.0": ["grapher"], "13.9 13.1 9.8": ["preventor"], "15.0 1.8 19.2": ["neckers"], "7.8 6.9 5.4": ["independencia"], "7.0 6.9 1.6": ["eol"], "9.8 6.8 11.4": ["neckware"], "-1.0 -1.7 3.6": ["adresse"], "3.0 10.6 13.2": ["bikable"], "10.6 16.7 10.7": ["noscript"], "17.8 2.4 5.9": ["bigbox"], "10.7 12.6 35.1": ["masu"], "-8.4 7.3 4.7": ["misconducted"], "16.4 7.4 32.2": ["piedra"], "9.7 10.7 36.7": ["beachgrass"], "-1.5 -7.1 0.4": ["resear"], "0.6 7.4 1.7": ["safeharbor"], "-5.1 13.1 3.6": ["antianginal"], "2.7 15.8 18.8": ["enterobacter"], "19.7 9.3 9.9": ["phototypesetting"], "0.3 3.5 3.0": ["acte"], "12.5 7.2 11.5": ["bantu"], "0.9 -1.9 12.0": ["urbain"], "4.7 1.8 14.4": ["dechrau"], "8.2 1.1 13.8": ["lupe"], "9.8 22.3 7.2": ["kiboko"], "7.8 19.8 5.4": ["roling"], "2.5 -0.0 3.4": ["etonogestrel"], "-4.2 -6.9 5.6": ["hydroxyprogesterone"], "-11.2 7.4 4.9": ["ordinated"], "0.9 23.4 4.9": ["compuserve"], "10.8 5.6 20.6": ["rouging"], "13.7 -2.0 -0.5": ["comefrom"], "2.8 3.7 13.2": ["saku"], "-1.5 -5.6 9.5": ["trict"], "5.1 4.3 21.8": ["dilo"], "8.4 2.3 6.4": ["bilayered"], "-4.3 10.8 7.3": ["saza"], "2.9 1.8 1.6": ["tortiously"], "6.8 10.4 11.8": ["thereselves"], "5.4 2.5 2.7": ["counterstrategies"], "9.0 11.7 8.5": ["substantia"], "4.5 9.7 18.9": ["hefe"], "16.2 15.3 14.5": ["tages"], "12.3 8.4 9.6": ["admix"], "5.2 6.6 18.3": ["erecta"], "10.1 5.2 5.4": ["orbi"], "13.8 6.7 7.2": ["promi"], "4.5 -11.2 11.1": ["phr"], "9.7 5.6 4.9": ["rendimiento"], "-5.6 2.0 4.0": ["oversales"], "0.9 7.2 10.6": ["submandibular"], "12.3 8.6 9.6": ["lapilli"], "2.0 5.4 0.1": ["hemmorhage"], "13.1 -2.0 22.9": ["hoofstock"], "3.4 10.5 20.7": ["reira"], "6.9 -6.6 6.9": ["uce"], "5.6 4.6 12.0": ["buttondown"], "19.4 25.3 26.8": ["scaredy"], "-0.8 5.0 -4.1": ["visitorial"], "2.0 3.7 14.0": ["lokal"], "19.3 -2.1 6.1": ["fluoroproducts"], "7.2 13.1 14.7": ["gaano"], "4.1 14.2 24.2": ["adai"], "4.3 0.8 6.3": ["propios"], "-0.9 2.2 1.2": ["videojournalists"], "-3.8 7.4 12.3": ["accretable"], "14.1 10.4 19.3": ["wowie"], "5.3 1.0 11.3": ["siglo"], "-5.7 0.5 14.5": ["dalaga"], "4.4 8.1 16.9": ["importin"], "0.8 6.3 7.6": ["tirement"], "11.5 -2.2 3.5": ["hostless"], "18.8 5.5 40.0": ["fumet"], "-2.3 10.8 11.8": ["onegame"], "15.6 15.6 11.3": ["noindex"], "18.7 17.9 24.2": ["longships"], "9.3 5.7 21.7": ["salisbury"], "6.6 8.1 15.8": ["naririnig"], "-0.5 9.6 10.5": ["noncardiovascular"], "-3.2 23.7 6.4": ["eretz"], "22.7 23.5 29.0": ["speciman"], "-0.7 -2.9 -2.8": ["professionnelle"], "21.5 11.1 12.2": ["segmentas"], "2.4 7.9 3.8": ["perezhilton"], "-4.5 8.5 4.0": ["gion"], "15.3 2.5 14.3": ["makara"], "-4.5 4.5 8.3": ["cervicovaginal"], "11.4 6.3 27.6": ["piquillo"], "5.9 -4.1 -3.0": ["upgradings"], "8.9 -5.3 8.9": ["xed"], "13.3 12.0 12.1": ["skirtsuits"], "-3.9 -1.6 5.6": ["codal"], "3.8 16.3 14.6": ["lieber"], "-2.1 -0.5 -11.7": ["ources"], "-3.6 9.5 2.8": ["nonforcible"], "5.4 14.7 19.1": ["centage"], "14.1 9.6 0.4": ["runflat"], "7.0 18.5 16.4": ["noooooooo"], "4.6 2.9 12.8": ["tators"], "1.4 0.2 9.5": ["forrester"], "0.2 13.3 4.4": ["baumannii"], "7.1 9.2 7.2": ["unserem"], "18.5 12.6 9.0": ["nefos"], "15.7 16.3 19.3": ["solenodon"], "3.5 9.1 6.7": ["winddown"], "19.4 -1.2 5.6": ["ifc"], "16.9 7.9 9.6": ["boybander"], "-5.3 15.8 3.0": ["compellable"], "11.6 -6.8 -1.2": ["matics"], "-3.8 -1.4 15.2": ["bacteriologically"], "3.0 0.5 10.4": ["cyfnod"], "6.4 5.0 13.6": ["kunin"], "-1.5 -1.9 3.4": ["approv"], "14.7 0.5 27.4": ["bassett"], "5.8 1.9 14.5": ["nashua"], "1.5 -6.7 5.5": ["ghad"], "19.6 4.7 20.1": ["manzana"], "2.1 -1.5 10.3": ["prounced"], "7.4 6.2 12.0": ["parvum"], "11.9 6.8 28.6": ["ricers"], "2.0 11.8 12.8": ["kies"], "0.4 8.6 10.0": ["stackup"], "0.3 9.0 4.2": ["tegafur"], "0.9 -0.4 5.0": ["edd"], "8.1 6.4 10.7": ["kainate"], "4.3 9.2 7.8": ["pralidoxime"], "5.3 12.7 13.6": ["calprotectin"], "15.1 1.0 17.4": ["fluo"], "7.8 6.1 24.6": ["coastally"], "0.4 7.0 1.6": ["achillies"], "5.2 10.7 12.5": ["coff"], "10.4 1.7 -0.8": ["sda"], "5.8 1.2 10.5": ["normes"], "7.4 1.3 13.5": ["unchlorinated"], "4.3 9.4 18.9": ["panawagan"], "13.2 5.2 12.5": ["overmold"], "11.9 15.0 5.5": ["famiily"], "5.8 2.5 8.6": ["nondriver"], "6.3 9.7 7.8": ["empt"], "10.4 18.5 7.4": ["shearography"], "7.2 -7.7 7.1": ["sharehold"], "11.4 7.4 20.4": ["asiatica"], "3.4 11.9 14.2": ["porttitor"], "3.7 7.4 3.6": ["leftarm"], "6.1 10.9 6.7": ["taskers"], "6.2 11.0 16.5": ["neuropsin"], "9.5 9.5 12.3": ["phylactery"], "6.9 5.3 6.4": ["celles"], "15.3 0.3 12.3": ["nonstore"], "10.2 4.6 12.5": ["divos"], "8.6 3.5 12.9": ["zotarolimus"], "10.8 21.1 13.6": ["neophobic"], "1.2 13.8 -0.5": ["nonexplicit"], "12.7 18.5 16.4": ["tenebrae"], "-4.2 -2.1 -2.0": ["documen"], "13.9 12.4 11.1": ["hooing"], "9.2 14.7 17.9": ["upness"], "-3.3 1.9 13.6": ["tanggapin"], "4.9 3.5 12.4": ["deoxycholate"], "2.5 5.0 10.1": ["nyong"], "0.4 13.8 12.5": ["flufenacet"], "-2.1 5.7 2.5": ["dorzolamide"], "3.5 -0.1 5.5": ["objec"], "1.9 2.1 9.0": ["quotidien"], "7.3 5.3 21.8": ["putrescible"], "7.6 16.0 16.2": ["hakanasa"], "6.0 2.3 -6.5": ["sseldorf"], "6.9 9.3 15.7": ["jamma"], "-0.8 0.1 -2.3": ["optees"], "-4.4 1.5 6.5": ["reagrding"], "8.9 6.0 6.5": ["resynthesis"], "6.0 7.2 20.9": ["tobiano"], "3.4 8.3 14.5": ["coppin"], "9.5 4.3 5.6": ["crossdock"], "2.3 7.5 9.5": ["scorecentre"], "25.1 22.2 30.0": ["cochonnet"], "2.2 -1.6 -2.5": ["fournisseur"], "2.8 5.6 4.1": ["papular"], "-3.1 2.9 10.8": ["rti"], "-4.2 8.6 4.7": ["monocytic"], "9.5 15.0 10.9": ["chinky"], "14.4 14.0 16.3": ["smilier"], "9.4 6.6 10.8": ["autoridades"], "-6.3 2.4 5.4": ["kishore"], "-7.4 -2.1 -2.4": ["clinicial"], "4.1 10.0 15.8": ["tobi"], "0.6 -5.2 -5.8": ["idation"], "13.0 12.2 13.9": ["texpat"], "22.4 5.9 0.5": ["vanmaker"], "6.3 3.5 -2.2": ["offiziellen"], "6.9 1.2 5.8": ["keratoprosthesis"], "4.3 2.1 11.8": ["stolin"], "10.4 -2.3 8.9": ["triperoxide"], "-2.8 -0.7 -2.2": ["phenylbutyrate"], "2.3 16.4 2.7": ["sarsanghchalak"], "6.6 8.7 8.5": ["canalising"], "3.8 3.4 3.8": ["myaccount"], "19.6 16.5 6.3": ["kast"], "14.9 12.7 15.8": ["horreur"], "9.3 2.7 11.5": ["jayz"], "8.4 5.3 9.4": ["presentar"], "11.0 18.3 26.1": ["vulpes"], "-3.5 3.0 6.6": ["caths"], "4.7 1.5 6.3": ["microcapillary"], "19.3 21.9 11.0": ["rappeled"], "16.1 13.1 20.1": ["bodyblock"], "-10.5 0.1 -3.5": ["rovide"], "19.8 17.5 11.1": ["baggery"], "5.9 8.0 16.2": ["dums"], "10.4 13.0 15.8": ["prodders"], "-0.5 4.4 10.0": ["iobenguane"], "-4.2 2.8 3.3": ["pbb"], "16.4 24.0 11.1": ["berobed"], "8.5 14.6 17.3": ["mauris"], "1.8 3.1 6.4": ["pacto"], "4.5 4.0 14.7": ["elow"], "17.9 5.0 31.0": ["kunimasu"], "11.7 -0.1 -7.0": ["sporitelna"], "8.4 3.7 0.1": ["triunfo"], "-2.3 -4.1 3.1": ["pantiliners"], "5.6 11.5 18.3": ["bangko"], "-6.0 4.7 6.7": ["hyposmia"], "12.3 9.9 10.8": ["universalis"], "-7.1 8.5 -0.3": ["nied"], "9.1 10.1 14.1": ["viscounts"], "1.2 2.0 12.6": ["pelikulang"], "19.8 4.7 25.4": ["emmental"], "10.9 -0.0 12.6": ["iniciativa"], "6.9 7.9 20.4": ["bumaba"], "-2.4 9.2 6.8": ["polycyclic"], "-3.9 23.0 -3.0": ["shaykhs"], "4.9 15.0 0.0": ["uncertainness"], "12.5 -6.3 7.4": ["levelization"], "9.6 2.8 7.2": ["apotheke"], "-0.3 -4.8 7.0": ["heum"], "21.9 18.9 12.0": ["nothingburger"], "19.5 11.5 8.3": ["unmanufactured"], "-2.4 17.7 -1.7": ["velayat"], "4.3 8.8 8.2": ["nonpatient"], "0.2 10.9 9.1": ["permettant"], "11.2 -0.1 18.7": ["embarcaciones"], "9.2 -3.1 -3.7": ["namesti"], "8.9 9.6 3.4": ["barnraising"], "7.7 1.5 0.9": ["deductability"], "3.0 -0.3 7.1": ["abre"], "-6.2 -3.2 1.1": ["manageme"], "13.5 13.0 23.0": ["kiev"], "0.3 -10.2 7.0": ["depar"], "8.8 23.4 -2.3": ["beiing"], "7.0 7.9 3.4": ["antimonide"], "14.2 5.1 15.5": ["heelflip"], "11.4 19.0 7.7": ["ramjets"], "3.2 7.6 16.0": ["penser"], "7.0 12.9 17.0": ["overspender"], "7.7 -0.8 5.1": ["endocrinologic"], "-10.3 9.9 1.0": ["requestion"], "11.0 9.8 1.0": ["anacubis"], "1.5 10.9 7.1": ["samo"], "17.3 2.3 21.6": ["foetida"], "9.8 14.8 21.5": ["termino"], "11.3 2.2 9.1": ["fecta"], "11.9 5.0 14.2": ["slickens"], "4.0 1.8 6.8": ["preacquisition"], "8.7 12.9 18.6": ["paradoxus"], "2.6 7.3 4.6": ["eclogitic"], "22.5 14.2 9.9": ["prolate"], "9.7 6.9 11.8": ["nauseum"], "19.1 -0.9 7.1": ["aplicaciones"], "7.3 10.4 4.6": ["ustomers"], "11.3 4.4 10.3": ["grise"], "4.6 11.4 10.3": ["bhakts"], "4.5 -2.0 4.0": ["epicondylitis"], "6.5 4.3 12.2": ["subpanels"], "2.4 -5.4 -9.4": ["awyers"], "4.7 -0.7 6.7": ["humaines"], "5.9 30.9 4.3": ["adversarially"], "12.1 15.3 5.9": ["tsks"], "0.6 19.3 5.8": ["ungrudging"], "2.3 -2.4 13.8": ["porsyento"], "16.5 1.5 9.1": ["vomica"], "10.7 1.5 14.5": ["difrifol"], "14.5 -1.7 7.6": ["pipemaking"], "8.3 -0.2 4.8": ["accra"], "20.6 -3.5 7.2": ["shutterings"], "15.0 9.8 11.6": ["regassified"], "3.7 7.8 14.0": ["chasteberry"], "1.6 4.1 3.1": ["pourra"], "14.6 11.2 29.8": ["draco"], "-4.5 9.2 3.6": ["epithelialization"], "3.7 0.2 3.8": ["ithaca"], "10.7 2.8 14.6": ["superabrasive"], "12.1 10.1 20.6": ["fontanelle"], "2.8 -3.4 -3.2": ["catazine"], "11.3 0.4 0.6": ["abn"], "4.0 3.8 18.8": ["laki"], "1.6 8.0 15.7": ["precalculated"], "3.7 3.3 -0.4": ["hyperinsulinemic"], "11.0 2.1 7.6": ["groundbreakingly"], "5.7 15.5 -0.6": ["vivisectionists"], "8.3 7.7 3.3": ["blindings"], "9.5 -4.0 6.7": ["volumen"], "5.1 8.9 18.5": ["apocrine"], "8.3 9.4 12.0": ["nonthrowing"], "9.6 17.1 13.4": ["bikin"], "8.9 19.1 2.4": ["molestors"], "4.1 8.4 18.6": ["ipakita"], "7.9 1.9 11.0": ["zt"], "-3.7 6.1 8.3": ["firesetting"], "21.5 11.1 20.2": ["fooseball"], "19.1 -2.7 28.1": ["krispy"], "6.4 13.2 4.5": ["cits"], "3.3 19.5 1.8": ["serius"], "18.1 12.5 31.7": ["lehua"], "14.4 24.0 19.4": ["miry"], "6.7 6.6 7.5": ["sommes"], "12.2 16.8 12.1": ["amenaza"], "10.3 15.6 29.7": ["nuoc"], "5.0 3.0 7.7": ["adeno"], "14.2 -3.0 4.5": ["antritrust"], "9.1 -5.0 10.0": ["fuente"], "-5.5 4.9 12.6": ["agropolitan"], "2.2 -0.9 -5.2": ["kdb"], "9.3 11.5 -1.7": ["paens"], "4.9 12.8 6.2": ["responsorial"], "8.8 7.1 10.4": ["relaciones"], "4.3 -5.6 7.3": ["secondaire"], "10.1 1.1 3.0": ["gasbuddy"], "4.0 -3.2 9.5": ["enchancing"], "9.2 13.2 20.1": ["leapin"], "9.2 12.8 22.2": ["kapal"], "-0.9 14.0 12.6": ["ascochyta"], "4.1 7.1 11.1": ["elecciones"], "5.9 5.3 14.1": ["tryptic"], "2.4 16.0 10.1": ["keratomileusis"], "8.5 15.1 17.8": ["novi"], "12.9 3.2 15.0": ["suficiente"], "24.9 13.7 26.6": ["wriggler"], "11.4 12.7 8.7": ["gegeben"], "11.6 9.9 24.7": ["floatopia"], "-4.1 8.9 4.7": ["bandhan"], "-2.7 5.2 -3.9": ["haveyoursay"], "18.9 6.7 33.0": ["serow"], "12.0 5.7 6.4": ["entwickeln"], "-3.9 -11.5 -5.0": ["rehn"], "1.6 1.7 8.5": ["buls"], "-1.8 7.8 9.9": ["bindover"], "18.3 19.8 9.5": ["hardpacked"], "8.5 5.2 6.8": ["photoessay"], "3.9 9.4 5.4": ["assulting"], "8.3 3.4 14.4": ["georges"], "2.8 19.8 3.7": ["paveway"], "-2.7 -1.0 7.5": ["nonprice"], "10.3 2.6 15.6": ["rickettsia"], "6.6 -1.8 13.1": ["opciones"], "11.8 -5.8 2.1": ["unidades"], "3.2 3.5 13.1": ["shey"], "0.0 7.8 1.1": ["dichloroethylene"], "6.4 -4.8 11.2": ["amlwg"], "15.3 15.0 35.0": ["placoderm"], "17.4 18.8 10.1": ["eyries"], "6.8 7.5 8.8": ["demyelinated"], "-0.3 18.8 13.5": ["unidirectionally"], "17.5 23.0 13.3": ["straddlers"], "-5.5 9.8 2.8": ["tranylcypromine"], "3.1 12.7 10.2": ["testate"], "8.0 -2.3 2.7": ["inance"], "6.5 6.1 17.3": ["ellie"], "2.6 4.7 8.5": ["thioester"], "8.7 13.3 27.8": ["cavendish"], "21.2 5.1 18.5": ["dessins"], "-7.2 -10.8 5.5": ["itation"], "10.1 6.1 19.0": ["reinhardtii"], "12.9 3.3 17.7": ["pallasite"], "1.9 4.7 6.9": ["gini"], "10.3 14.7 24.1": ["palatte"], "-5.0 15.3 0.2": ["ilitary"], "6.0 5.7 13.6": ["toprol"], "7.9 -1.2 11.6": ["cefprozil"], "4.1 7.8 10.2": ["chaman"], "-5.2 3.6 3.6": ["enzymic"], "11.8 4.3 13.7": ["lapelled"], "2.0 6.7 12.4": ["bansang"], "9.5 9.3 29.9": ["banty"], "7.2 13.5 13.6": ["innominate"], "9.6 15.0 8.3": ["godt"], "6.3 12.7 11.6": ["nontariff"], "12.5 2.7 32.0": ["suan"], "6.9 5.9 9.1": ["bwa"], "-0.2 7.3 18.0": ["lifevest"], "2.1 14.4 12.0": ["tektaktyks"], "10.2 15.8 9.1": ["regretfulness"], "2.8 1.4 8.5": ["importanti"], "7.5 8.7 9.9": ["merrill"], "0.6 6.7 -0.2": ["kurz"], "-4.8 9.8 9.2": ["varietally"], "5.5 7.0 13.2": ["puertos"], "-0.0 4.7 0.8": ["microspectrophotometer"], "9.8 8.3 9.3": ["heptyl"], "9.7 7.6 14.7": ["klee"], "3.0 18.1 7.4": ["wrld"], "0.1 -1.2 1.8": ["nior"], "8.9 7.2 22.8": ["colorblocking"], "8.8 12.5 21.5": ["durrr"], "-6.6 14.5 3.0": ["inspectable"], "2.5 4.1 5.4": ["tenu"], "25.7 12.4 6.5": ["puters"], "19.7 38.8 3.2": ["tankbuster"], "4.4 1.6 22.3": ["bivoltine"], "5.2 12.4 16.5": ["sacre"], "4.1 15.5 7.3": ["plomo"], "-2.4 3.1 3.4": ["unemancipated"], "13.3 13.8 11.6": ["superantigen"], "12.6 1.8 5.5": ["insurancelike"], "2.5 4.4 13.6": ["rehiyon"], "3.7 1.2 4.4": ["ressed"], "8.1 3.7 5.8": ["darauf"], "4.6 -11.3 -1.0": ["rman"], "8.5 17.0 12.6": ["mately"], "2.8 -4.3 3.8": ["necesitan"], "9.7 -1.4 14.2": ["goddesslike"], "6.3 7.2 29.7": ["beatis"], "12.8 23.2 4.6": ["manmohan"], "16.4 18.8 15.4": ["gearsets"], "2.0 2.5 4.0": ["andlong"], "13.1 6.1 11.3": ["estrategia"], "20.3 16.5 15.5": ["bosu"], "23.3 -2.2 3.7": ["wholsesale"], "4.5 -0.1 16.7": ["bilyon"], "6.1 5.6 10.8": ["turnaway"], "12.8 3.1 23.0": ["freddo"], "11.7 13.6 23.5": ["faddist"], "-0.2 6.5 0.7": ["noobligation"], "0.4 6.0 9.6": ["lutte"], "-0.4 3.6 2.1": ["bronchodilatory"], "-0.8 4.5 18.6": ["nakukuha"], "-4.6 2.4 13.9": ["kutchery"], "12.7 -0.4 6.0": ["samen"], "10.1 12.0 6.8": ["bogeyless"], "3.0 7.4 12.7": ["petersburg"], "22.6 8.2 12.7": ["disporting"], "7.1 5.6 6.7": ["aei"], "3.5 8.9 9.2": ["chromatid"], "-6.6 7.0 -3.4": ["lect"], "9.1 16.7 1.3": ["naksa"], "11.5 9.7 15.7": ["pendula"], "9.8 9.5 14.4": ["sinusoid"], "-4.4 0.6 5.1": ["cws"], "-5.3 6.3 -3.8": ["towa"], "-6.1 14.1 4.1": ["qesas"], "10.7 14.4 -2.1": ["junge"], "3.1 3.1 6.8": ["allein"], "3.9 7.9 6.8": ["ingrowing"], "-0.6 13.8 6.3": ["sequitur"], "-4.1 8.4 -5.4": ["acredited"], "16.6 8.7 -2.0": ["bodyspray"], "6.6 16.8 2.7": ["wisked"], "10.9 3.8 19.3": ["dooby"], "8.6 5.8 4.7": ["otherrisks"], "-2.5 6.7 11.9": ["nahn"], "12.8 3.3 4.8": ["ventas"], "4.8 6.7 7.9": ["underrun"], "25.3 -5.2 5.8": ["carpetmaker"], "-1.4 10.4 21.8": ["chuka"], "2.0 4.7 13.9": ["ymateb"], "9.6 -2.0 12.7": ["oferta"], "17.5 10.4 19.2": ["patoot"], "2.4 2.2 8.8": ["hispana"], "4.0 1.0 16.6": ["llys"], "5.9 4.5 -0.2": ["photolab"], "2.8 -0.5 9.4": ["antirejection"], "14.8 19.9 16.0": ["immitating"], "3.0 0.6 -0.7": ["microsimulation"], "-3.4 4.3 6.0": ["kaul"], "0.2 10.6 24.4": ["packaway"], "22.3 13.2 4.4": ["obscura"], "7.5 12.2 10.2": ["catalepsy"], "12.8 20.9 6.8": ["powershot"], "5.6 2.8 12.5": ["kunst"], "2.6 -2.1 17.4": ["corsos"], "22.6 15.2 10.2": ["hubless"], "0.3 6.0 3.1": ["intv"], "6.1 12.2 37.0": ["clingstone"], "0.8 5.2 10.3": ["malinis"], "14.0 15.0 10.0": ["huppah"], "14.3 6.9 40.7": ["scallopine"], "9.4 21.1 2.7": ["walky"], "5.2 3.8 8.6": ["davantage"], "12.9 12.6 5.0": ["carbolic"], "5.8 0.5 9.5": ["musico"], "5.5 26.7 9.3": ["indifferentism"], "-3.8 12.0 -3.3": ["banerjee"], "6.4 22.8 1.1": ["asigned"], "3.0 6.4 19.0": ["whah"], "-0.6 7.0 17.8": ["lungsod"], "0.3 -6.1 1.9": ["presigned"], "17.7 -6.2 10.1": ["andconstruction"], "2.1 -0.1 12.7": ["borrowable"], "4.9 13.5 7.3": ["camerapeople"], "-5.0 1.3 9.4": ["middleton"], "-0.2 0.2 8.9": ["nbr"], "7.5 9.7 7.4": ["geobelt"], "20.0 12.5 15.0": ["paintless"], "-5.6 10.9 3.1": ["notas"], "9.5 14.1 13.0": ["anons"], "3.7 3.3 16.3": ["carica"], "4.8 2.4 12.5": ["pauvre"], "6.7 15.4 19.4": ["gravedigging"], "5.7 12.7 4.7": ["starcrossed"], "1.2 -13.8 -0.5": ["unstarred"], "5.7 0.3 2.8": ["hdfc"], "2.8 -0.9 8.2": ["craniopagus"], "0.6 4.6 11.1": ["contendere"], "9.5 18.2 15.8": ["tourette"], "2.8 11.4 3.8": ["evacation"], "6.4 10.8 1.1": ["moteur"], "19.3 22.6 25.7": ["dunder"], "12.4 10.5 5.7": ["hyperguard"], "15.3 3.8 7.9": ["boujou"], "13.4 10.6 14.8": ["dizziest"], "1.6 0.6 -0.1": ["hypobaric"], "15.6 -1.4 12.3": ["pte"], "-1.6 5.7 6.6": ["anam"], "3.5 10.2 3.2": ["suppurative"], "6.0 1.2 -1.7": ["fourni"], "3.3 15.2 1.4": ["potentiators"], "11.1 0.8 7.6": ["crimi"], "0.9 -3.5 4.1": ["groh"], "-6.5 2.3 5.6": ["plerixafor"], "7.2 25.4 15.1": ["meshuga"], "1.3 -0.8 15.7": ["grado"], "2.0 0.1 8.7": ["marys"], "-0.5 1.1 2.0": ["vahn"], "15.0 15.9 17.2": ["redman"], "-4.3 4.4 2.0": ["pollbooks"], "-5.4 7.7 4.5": ["polymicrobial"], "11.3 24.0 6.2": ["tahrir"], "14.0 18.5 24.3": ["tussocky"], "15.9 8.2 22.1": ["ziploc"], "0.4 2.8 10.4": ["visant"], "14.4 9.3 14.9": ["ampler"], "8.3 16.7 28.6": ["hirsuta"], "9.3 3.8 6.5": ["bouncily"], "5.4 4.3 12.3": ["cuento"], "8.9 9.9 14.1": ["hackled"], "-0.7 -3.6 0.1": ["billig"], "-0.3 7.7 10.2": ["stata"], "15.0 18.6 12.3": ["uncaptioned"], "5.1 1.1 19.6": ["payo"], "-11.2 -5.5 6.2": ["stur"], "-5.6 -2.0 0.2": ["vectorless"], "9.2 -3.3 -1.6": ["imited"], "8.0 5.5 1.6": ["appeallate"], "0.4 -2.3 2.6": ["ogether"], "13.7 2.8 16.9": ["cumshots"], "16.5 20.5 47.6": ["spottail"], "4.4 7.0 21.1": ["hyang"], "19.9 -0.6 8.9": ["memorobilia"], "-5.6 -2.0 9.4": ["unannualized"], "13.2 7.4 8.6": ["geithner"], "5.3 -9.4 11.7": ["mohn"], "5.6 2.9 21.7": ["kulay"], "17.6 0.9 14.0": ["balconette"], "15.8 17.6 20.8": ["splashdowns"], "10.6 3.4 15.1": ["dynactin"], "2.8 -0.5 12.6": ["cetyl"], "13.1 5.6 20.2": ["nivalis"], "7.3 7.0 15.4": ["sambucas"], "11.7 7.1 10.4": ["accentless"], "10.2 -1.9 8.5": ["concierto"], "3.3 16.1 16.0": ["ingat"], "15.9 12.1 19.8": ["faccum"], "-1.2 1.8 -2.0": ["erations"], "-2.5 0.9 12.4": ["ritin"], "9.5 -1.0 6.9": ["outils"], "-0.2 -1.1 -5.5": ["blogozine"], "1.2 -9.6 10.8": ["diacetate"], "10.0 -1.4 -1.7": ["multijet"], "-9.2 -2.0 0.8": ["admis"], "9.7 7.1 4.1": ["journalistes"], "1.9 6.0 9.9": ["letzte"], "11.1 0.9 4.1": ["sify"], "12.1 6.7 11.6": ["pruriently"], "8.8 5.7 12.1": ["urbs"], "-7.7 3.3 3.6": ["mercaptopurine"], "12.3 6.1 29.8": ["musculus"], "11.4 4.1 5.8": ["tsking"], "-1.2 4.9 8.1": ["grmg"], "11.3 12.7 4.1": ["electrophotography"], "10.3 2.5 9.5": ["poche"], "-0.2 13.4 8.3": ["antispeculation"], "8.9 5.1 17.7": ["nombres"], "6.9 -9.1 5.9": ["progetto"], "7.4 -1.3 13.9": ["theatr"], "7.8 -4.6 12.7": ["bodiced"], "12.2 5.7 12.2": ["micronucleus"], "14.1 -1.4 1.3": ["revocatory"], "-1.0 10.7 10.7": ["bytecodes"], "11.8 16.9 13.9": ["seismologic"], "-3.7 10.5 6.6": ["disfellowship"], "10.9 1.4 7.6": ["hechos"], "-6.3 -0.9 0.4": ["dors"], "4.2 -15.3 4.4": ["menting"], "6.6 -1.7 13.3": ["bontril"], "9.1 5.3 7.4": ["venezolanos"], "3.1 -3.6 20.2": ["backcross"], "8.3 5.9 10.0": ["dommage"], "26.7 16.8 8.9": ["cyberintrusions"], "9.2 1.5 5.3": ["wallcharts"], "-9.0 0.3 8.7": ["stown"], "-2.4 9.4 18.6": ["kinakailangan"], "8.3 5.3 10.9": ["dessous"], "3.4 14.2 5.8": ["northeasterner"], "6.7 10.4 7.8": ["organophosphorous"], "2.3 8.4 14.9": ["tahimik"], "-0.3 8.0 20.5": ["kurang"], "6.2 9.0 14.6": ["territorio"], "9.2 6.5 36.2": ["massaman"], "1.6 -1.6 8.2": ["levoleucovorin"], "12.1 9.0 16.9": ["cuticular"], "8.3 3.6 14.6": ["maran"], "5.2 3.9 7.0": ["larly"], "3.9 5.6 5.7": ["soundscience"], "8.3 -6.2 22.3": ["juno"], "8.5 5.2 14.3": ["redesigner"], "6.8 4.9 15.5": ["endocasts"], "3.6 -0.5 18.1": ["mdx"], "4.0 -1.6 4.3": ["collegesports"], "22.5 3.0 25.4": ["barm"], "6.3 7.7 17.8": ["dwayne"], "7.9 22.2 9.4": ["intratheater"], "12.6 10.5 13.6": ["handfasting"], "-2.0 8.5 0.9": ["envers"], "0.3 -5.2 21.9": ["andres"], "7.9 4.1 0.7": ["gyrotonic"], "2.4 17.2 10.2": ["applicati"], "13.3 6.4 20.3": ["panchami"], "13.7 15.7 13.7": ["traficking"], "-6.2 8.2 3.7": ["structed"], "7.7 10.2 6.8": ["nonautistic"], "6.1 10.6 10.2": ["intercranial"], "5.7 6.3 8.2": ["reer"], "-1.1 3.2 12.2": ["debo"], "13.5 -3.0 16.3": ["aftersun"], "6.2 27.5 15.8": ["aleikum"], "-1.8 8.8 11.1": ["extralabel"], "1.3 7.9 10.8": ["multiforme"], "8.4 7.2 8.4": ["odometry"], "-0.4 13.4 2.6": ["alleygating"], "8.3 5.5 21.3": ["vermi"], "10.3 19.6 6.4": ["duodecim"], "2.3 7.9 1.1": ["farwest"], "1.7 2.1 26.9": ["makhni"], "6.4 2.1 11.7": ["countryfied"], "0.1 -0.5 -3.1": ["enteo"], "2.8 -0.8 3.0": ["oculoplastic"], "-7.5 -0.5 8.9": ["kaiwhakahaere"], "1.6 7.3 18.4": ["walkless"], "12.0 5.2 8.0": ["sinds"], "8.0 14.7 13.2": ["econonomic"], "7.4 7.7 11.3": ["guit"], "18.4 15.1 25.0": ["freakazoids"], "3.1 4.7 20.7": ["probinsiya"], "-4.9 0.9 -0.5": ["breathalyze"], "2.5 6.0 1.2": ["intergral"], "2.5 7.1 4.3": ["dirigeants"], "7.0 6.7 14.8": ["howell"], "6.7 4.7 1.8": ["croix"], "5.4 5.0 0.3": ["scrubdown"], "12.9 4.0 3.9": ["qualcomm"], "-2.0 3.7 9.0": ["rison"], "4.1 8.3 7.9": ["dichlorobenzene"], "5.1 8.1 6.2": ["phytoene"], "7.4 7.3 11.9": ["hypersalivation"], "11.2 5.0 29.2": ["unhusked"], "23.5 23.3 22.3": ["bladelike"], "5.0 7.9 12.2": ["iac"], "13.5 2.8 5.5": ["tcu"], "1.9 18.8 7.3": ["immigrantion"], "9.6 3.3 7.9": ["snmp"], "12.6 7.7 12.4": ["mudpots"], "17.6 9.6 12.3": ["grafedia"], "6.0 -0.1 8.1": ["servidor"], "13.7 9.5 5.8": ["machina"], "1.2 7.3 10.7": ["tingin"], "6.6 -2.7 14.5": ["tortuosum"], "7.6 2.9 4.6": ["installiert"], "11.0 -2.3 9.4": ["dioxides"], "5.4 13.1 17.2": ["waggy"], "16.7 -3.6 9.2": ["ffatri"], "9.9 3.8 14.5": ["avere"], "23.3 22.9 23.2": ["germanica"], "12.8 13.7 12.9": ["multiprogram"], "-0.9 15.6 9.1": ["bahadur"], "1.6 0.5 18.6": ["meddwl"], "8.7 -1.4 8.4": ["phun"], "11.5 9.4 18.2": ["lejos"], "2.5 8.5 14.5": ["kapayapaan"], "10.4 1.9 13.8": ["storia"], "4.1 4.9 13.4": ["yersinia"], "17.9 3.5 12.0": ["chemi"], "0.3 5.4 2.7": ["gradu"], "17.6 4.6 22.4": ["nola"], "-1.8 5.5 22.5": ["putih"], "-4.0 7.1 5.8": ["timelined"], "2.8 5.1 12.9": ["dignissim"], "-1.4 1.8 -0.7": ["uding"], "3.1 8.2 9.5": ["demonstrat"], "8.1 -7.0 7.7": ["arden"], "-5.2 1.3 7.5": ["debuter"], "17.0 21.1 21.7": ["quelea"], "-1.2 9.3 7.6": ["advanceable"], "8.9 16.1 12.8": ["frnd"], "1.7 8.3 3.7": ["rematerialised"], "7.8 -1.8 9.6": ["bwysig"], "1.8 6.4 12.8": ["aleurone"], "11.4 2.9 8.7": ["halobutyl"], "3.2 3.1 15.2": ["malinaw"], "2.6 6.3 12.1": ["tanam"], "3.9 -10.0 9.1": ["worcestershire"], "3.9 5.8 6.9": ["mensaje"], "12.0 11.2 8.3": ["gering"], "11.7 6.3 8.5": ["cherche"], "1.7 2.9 9.0": ["tuig"], "14.8 6.1 16.4": ["inces"], "-9.2 6.3 0.3": ["procainamide"], "-4.2 12.2 6.0": ["interfacility"], "0.3 -6.4 10.3": ["schoolage"], "2.3 8.0 -2.0": ["pentazocine"], "13.4 14.8 7.8": ["shahrukh"], "4.3 1.3 13.1": ["motilin"], "5.4 0.9 16.4": ["kem"], "7.3 30.9 14.5": ["reconnoissance"], "7.7 14.8 10.2": ["outcheering"], "14.8 5.9 29.1": ["yums"], "1.2 8.2 18.1": ["malapit"], "-0.6 17.1 15.6": ["tefilin"], "15.9 16.0 12.5": ["guerdon"], "-5.6 9.2 18.7": ["submaster"], "3.6 -0.7 10.3": ["unconformably"], "3.0 -4.7 4.5": ["aorto"], "16.7 3.0 5.4": ["joropo"], "11.3 9.6 3.3": ["sclerostin"], "19.6 6.2 16.1": ["acity"], "-3.1 9.1 11.7": ["madu"], "-12.6 0.8 -2.3": ["colposcopic"], "-4.9 -4.3 0.4": ["futuretrust"], "3.8 12.4 7.4": ["juat"], "6.3 5.5 7.8": ["nolo"], "2.3 -0.9 -2.0": ["reconductoring"], "0.3 2.7 0.4": ["neuroactive"], "24.3 6.6 17.8": ["sinornithomimus"], "0.2 -2.4 -6.3": ["sls"], "9.5 -2.6 33.4": ["akami"], "3.5 12.7 8.3": ["crum"], "12.9 8.6 2.9": ["coalfired"], "-0.6 -2.8 18.7": ["tumaas"], "-0.4 -13.4 6.5": ["invita"], "-0.2 12.3 14.5": ["laicizations"], "16.0 2.7 23.6": ["cala"], "1.4 10.6 8.4": ["atives"], "6.5 6.9 3.5": ["photocouplers"], "4.5 5.6 15.1": ["conway"], "8.4 1.6 8.4": ["devenir"], "7.8 -4.2 5.3": ["toneladas"], "1.9 5.7 20.2": ["maz"], "18.3 13.8 36.5": ["sengi"], "9.0 -3.2 16.7": ["berkshire"], "6.5 8.8 10.0": ["benedictory"], "11.6 -2.3 14.7": ["freshinfo"], "-4.8 -3.0 -2.8": ["onds"], "11.3 16.3 15.9": ["liddell"], "3.1 9.0 23.7": ["glabrata"], "14.4 -0.5 10.5": ["pelites"], "11.6 9.2 14.8": ["seus"], "-3.6 5.6 8.5": ["bains"], "9.7 8.0 12.7": ["sayanti"], "-5.5 4.4 14.1": ["konti"], "0.0 -11.0 2.0": ["intratympanic"], "4.2 20.2 14.5": ["nicey"], "-3.7 13.7 7.9": ["fomento"], "12.8 8.1 12.5": ["sqare"], "8.7 30.7 4.1": ["separtist"], "2.1 -5.5 9.3": ["universitaire"], "27.1 10.0 31.6": ["bulkie"], "2.9 0.7 6.3": ["fendi"], "21.5 10.9 13.5": ["astrophe"], "4.8 8.8 21.2": ["kinabukasan"], "0.0 7.5 10.0": ["faecium"], "8.7 13.9 3.4": ["plasm"], "10.3 19.5 10.4": ["soweth"], "11.0 8.3 16.4": ["rhumbas"], "6.6 4.2 7.0": ["digibet"], "9.6 8.6 4.0": ["refleeting"], "21.1 9.7 38.2": ["midriver"], "9.8 13.9 14.8": ["bheil"], "22.3 10.1 12.1": ["microengineering"], "15.0 20.2 26.8": ["invicta"], "2.7 11.7 22.6": ["rogan"], "8.3 5.3 12.9": ["zmien"], "6.9 10.3 21.4": ["sixed"], "-1.3 3.1 7.4": ["voltammetry"], "7.9 -2.1 11.3": ["lys"], "5.1 17.7 8.8": ["imation"], "-3.1 -5.0 10.7": ["aelod"], "-0.1 15.3 3.6": ["conven"], "5.7 4.9 5.0": ["ietf"], "9.8 1.7 4.3": ["laatste"], "1.9 -2.1 6.4": ["dling"], "1.4 8.2 11.3": ["shana"], "20.5 11.9 26.7": ["mousedeer"], "10.5 8.3 9.9": ["erreur"], "10.3 4.3 7.2": ["kihs"], "16.7 8.6 28.9": ["buttercreams"], "10.5 6.5 4.5": ["grubbily"], "13.0 13.9 18.2": ["photosynthetically"], "-5.0 -6.4 4.5": ["ligations"], "2.6 12.2 12.7": ["dutta"], "7.4 7.7 27.2": ["curcuma"], "16.5 -6.2 10.6": ["gluer"], "11.3 2.9 34.7": ["brule"], "-0.1 4.2 12.1": ["myxedema"], "7.8 3.8 7.7": ["eigene"], "10.8 0.5 17.8": ["gorau"], "-5.3 9.4 1.5": ["mpp"], "-3.7 2.6 0.4": ["thepoint"], "13.5 6.0 11.7": ["steeltown"], "6.1 3.2 15.3": ["lauric"], "0.2 13.9 20.3": ["labanan"], "12.8 19.9 9.1": ["deprecations"], "-6.8 4.2 7.7": ["syncopal"], "8.9 2.1 9.8": ["banques"], "16.6 4.6 7.9": ["microforces"], "-0.5 4.6 5.1": ["channelopathies"], "14.0 14.1 22.3": ["merrie"], "-5.5 7.1 -4.7": ["cardioverted"], "9.9 20.7 15.1": ["aaway"], "14.1 1.5 5.1": ["piattaforma"], "11.0 17.4 16.9": ["mustachio"], "1.1 3.6 11.6": ["tshwanetse"], "10.6 -4.8 9.3": ["plovidba"], "20.6 10.9 0.6": ["blooey"], "2.4 5.6 10.8": ["bacio"], "-1.4 0.5 9.1": ["gests"], "6.3 8.6 27.1": ["mammalogists"], "9.5 1.9 3.0": ["norme"], "7.9 14.2 7.1": ["disfigurations"], "6.8 9.5 18.4": ["gger"], "1.1 2.0 11.9": ["ordi"], "18.2 6.3 9.8": ["sliderule"], "4.6 10.6 0.9": ["minroity"], "-4.4 6.4 4.4": ["surchargeable"], "6.4 1.6 11.5": ["rikshaw"], "10.9 18.8 3.7": ["guarda"], "2.2 8.4 -6.1": ["oratorial"], "0.8 3.6 11.7": ["aplastic"], "5.7 11.0 14.1": ["pubsrtoast"], "11.5 1.6 10.1": ["encou"], "2.7 6.7 0.9": ["antirheumatic"], "5.4 3.7 4.0": ["sampark"], "2.0 18.2 6.5": ["possessional"], "9.5 5.3 15.3": ["grossology"], "11.5 1.6 12.8": ["wrinklier"], "4.0 -5.4 1.6": ["kef"], "10.0 1.9 12.8": ["gerber"], "11.2 16.4 15.6": ["ntse"], "-6.7 19.0 2.1": ["sabermetrically"], "6.7 2.6 13.1": ["documentos"], "2.6 -1.1 3.1": ["ournament"], "15.9 7.3 12.3": ["utiful"], "17.2 12.3 5.2": ["unreplaceable"], "-2.7 3.8 7.3": ["biocultural"], "5.1 -0.9 3.6": ["utilisateurs"], "-0.1 5.9 12.1": ["ellas"], "7.9 2.0 0.5": ["ministe"], "-3.9 3.9 2.8": ["limi"], "13.8 13.6 14.2": ["tingler"], "2.7 7.2 7.9": ["lenguaje"], "-11.8 3.8 9.1": ["endent"], "0.7 6.0 3.8": ["multitechnology"], "4.6 6.3 9.4": ["nonsquamous"], "-2.1 3.1 -0.9": ["urrent"], "20.8 3.4 11.4": ["commod"], "2.1 0.5 7.2": ["oters"], "5.1 26.7 9.1": ["counterblow"], "-0.8 16.4 5.3": ["nitish"], "20.6 3.8 11.7": ["fanfold"], "0.1 4.4 11.0": ["kabila"], "6.3 3.2 11.7": ["petanquers"], "16.5 3.0 32.9": ["daing"], "17.4 2.1 13.2": ["megamillion"], "6.5 9.8 12.7": ["changey"], "8.9 2.4 24.4": ["katsura"], "2.7 9.5 11.6": ["ghani"], "16.3 11.1 1.2": ["megafan"], "-2.7 21.7 -3.7": ["commmander"], "20.1 20.4 19.1": ["bursters"], "4.9 17.3 13.9": ["fidgetiness"], "16.0 20.1 25.4": ["thoraxes"], "11.9 4.7 4.6": ["bearingless"], "-3.3 0.6 15.6": ["ouevres"], "15.6 9.0 12.2": ["chefdom"], "5.5 10.5 17.2": ["malayi"], "13.4 15.8 13.5": ["tandav"], "4.2 14.4 9.8": ["shoer"], "7.2 1.9 9.1": ["prestazioni"], "-0.4 7.0 14.4": ["facilisis"], "5.2 2.5 15.1": ["intracorneal"], "7.5 20.0 10.6": ["terrritory"], "3.1 17.4 9.1": ["gunshops"], "-0.7 -0.5 7.2": ["suivant"], "9.2 6.2 14.1": ["magagaling"], "5.4 18.8 -1.0": ["interatomic"], "2.9 4.8 5.3": ["lezen"], "5.9 20.2 5.3": ["unmotorized"], "4.1 9.7 6.6": ["italo"], "-2.0 1.6 1.3": ["erence"], "5.7 -3.8 9.5": ["carboxymethylcellulose"], "13.1 11.7 12.8": ["dapperly"], "15.4 0.6 20.8": ["poma"], "3.3 2.3 2.9": ["postdraft"], "14.5 10.1 38.1": ["parslied"], "2.3 19.6 8.0": ["costimulatory"], "10.9 1.2 12.1": ["stockjudging"], "19.2 7.2 12.8": ["optofluidic"], "9.9 21.8 15.9": ["thaaththa"], "17.4 13.5 9.2": ["miserables"], "0.5 0.5 12.0": ["myoung"], "23.6 0.5 30.5": ["huevo"], "11.3 -4.3 9.2": ["iittala"], "5.1 16.4 2.9": ["warantless"], "3.6 13.6 10.9": ["nonbacterial"], "4.2 6.6 3.7": ["nonbonding"], "13.3 15.4 5.3": ["shilly"], "-0.2 -2.3 26.4": ["mangu"], "17.7 6.1 5.2": ["photoconductor"], "2.7 5.4 13.4": ["ombres"], "10.2 8.6 13.1": ["euthansia"], "3.3 1.6 13.7": ["tartaric"], "1.0 -2.9 11.7": ["actualmente"], "6.6 3.8 10.6": ["barbacks"], "5.2 -6.3 2.2": ["mpany"], "14.6 23.4 5.1": ["protecters"], "11.6 13.3 16.2": ["lovegrass"], "-4.7 1.5 12.2": ["reta"], "6.0 14.9 5.4": ["connaissance"], "8.2 10.0 17.3": ["neeche"], "4.9 0.7 8.2": ["deaminase"], "15.2 29.3 7.2": ["mongerer"], "-5.0 -1.2 11.6": ["emy"], "9.8 23.4 10.7": ["darwinism"], "16.9 2.8 19.1": ["sabretooth"], "0.6 11.4 12.2": ["essayer"], "9.9 4.1 23.5": ["rotundifolia"], "10.5 1.7 11.9": ["pretrail"], "7.3 23.4 11.7": ["spybase"], "6.9 -2.7 17.3": ["tivities"], "0.3 -7.1 6.7": ["nonvoluntary"], "-3.0 -5.9 2.2": ["ehk"], "3.9 15.7 27.3": ["knappers"], "1.5 -2.4 -1.4": ["magnetorheological"], "-0.3 -0.6 6.4": ["vais"], "25.8 5.2 27.1": ["eensy"], "1.2 0.6 -1.0": ["soutient"], "1.0 9.7 6.4": ["dayplanner"], "7.0 5.5 20.1": ["cheltenham"], "1.7 7.5 8.4": ["risques"], "10.6 -2.1 10.6": ["actif"], "2.3 9.8 -0.1": ["anjo"], "4.3 25.2 7.9": ["interclan"], "-3.1 23.3 8.1": ["yetzer"], "4.7 9.5 8.5": ["catarrhal"], "9.3 16.1 2.5": ["janus"], "3.2 4.9 6.7": ["tiwari"], "-3.6 3.2 -6.5": ["sint"], "1.2 4.0 10.3": ["standi"], "-9.3 3.6 6.1": ["tellme"], "12.5 11.8 13.3": ["confoundedly"], "11.6 12.0 9.1": ["auxetic"], "9.2 7.8 17.3": ["fection"], "12.9 12.0 13.5": ["crackback"], "2.3 5.4 6.0": ["erh"], "2.2 3.0 -0.7": ["fournir"], "5.5 4.9 -0.5": ["geospacial"], "8.2 9.4 9.1": ["metrodome"], "-15.2 8.5 -0.6": ["mination"], "15.7 6.4 31.8": ["chasseur"], "4.9 5.7 8.8": ["dicen"], "2.0 2.7 7.6": ["kollywood"], "6.9 6.9 8.4": ["nonconfirmation"], "0.9 9.5 1.3": ["deionized"], "-2.5 13.7 7.4": ["keling"], "6.4 2.2 4.6": ["interpositional"], "-0.7 2.6 4.1": ["esophagogastroduodenoscopy"], "23.2 13.2 15.3": ["keymat"], "7.6 16.0 13.7": ["puhleeze"], "4.8 -2.8 12.9": ["digwyddiad"], "4.7 5.2 5.9": ["sasta"], "-0.4 6.5 4.9": ["cbn"], "16.5 17.2 30.1": ["betony"], "1.7 -1.7 6.8": ["hthe"], "-4.2 3.2 3.4": ["parvalbumin"], "2.3 6.1 11.1": ["tendonosis"], "14.8 12.3 9.8": ["unrenewable"], "-7.2 15.9 8.9": ["antabuse"], "3.1 2.4 6.9": ["blic"], "6.9 6.0 35.4": ["fagioli"], "10.4 0.2 4.2": ["outserts"], "6.2 13.0 0.9": ["forwardto"], "8.3 2.6 -4.5": ["enricher"], "-8.2 9.5 5.2": ["sawal"], "2.5 6.8 2.1": ["ratethemusic"], "5.3 10.9 -2.8": ["tempore"], "21.5 17.5 37.1": ["hognose"], "1.6 4.1 12.6": ["wpa"], "7.8 8.0 2.5": ["sharm"], "6.3 -1.7 4.6": ["hydroxypropyl"], "-0.0 1.8 16.2": ["beke"], "2.4 -0.3 11.9": ["hrly"], "-7.9 -1.8 -2.8": ["anthroposophic"], "5.7 -6.3 2.0": ["tioning"], "14.2 2.2 8.0": ["hotshop"], "8.6 5.8 4.6": ["bicyclic"], "1.1 7.5 1.8": ["congenita"], "10.9 5.2 9.5": ["azine"], "2.0 5.4 4.7": ["nairobi"], "-5.9 1.1 -9.0": ["ordonnance"], "-3.9 4.0 3.9": ["hypernatremia"], "14.2 0.5 12.7": ["cakemaker"], "22.9 12.4 16.5": ["pricker"], "2.3 -0.1 8.0": ["dispositif"], "-3.1 -1.1 4.8": ["tenodesis"], "0.9 10.4 9.0": ["strophic"], "2.3 -1.7 2.2": ["advo"], "-2.7 1.7 18.8": ["rajmah"], "18.4 -1.3 8.4": ["cuesta"], "0.6 12.3 9.5": ["unsimulated"], "23.0 31.3 18.8": ["lombax"], "9.6 11.0 15.6": ["splittable"], "11.9 6.8 20.2": ["weensy"], "6.2 8.6 15.7": ["pasti"], "12.4 6.1 15.8": ["isostatic"], "5.7 3.2 6.5": ["xcode"], "2.3 4.7 2.9": ["egrips"], "19.0 10.5 38.7": ["gorgonians"], "-1.8 14.1 -2.1": ["mortgageable"], "-5.1 -0.2 -4.9": ["meier"], "-3.4 -6.5 1.3": ["laminectomies"], "-1.9 9.8 9.2": ["sumama"], "3.9 -3.2 12.6": ["siarad"], "12.8 4.0 2.3": ["murabahah"], "0.9 3.1 16.1": ["jeb"], "7.5 5.3 11.1": ["ealthy"], "4.7 0.7 16.1": ["inmigration"], "5.2 9.1 13.5": ["stolonifera"], "10.9 8.3 13.3": ["spookhouse"], "4.3 9.4 6.6": ["frisbie"], "-2.3 2.2 8.9": ["intraabdominal"], "5.2 0.5 6.9": ["royalwedding"], "8.6 9.8 15.8": ["samson"], "12.6 8.6 7.7": ["antireflection"], "-4.3 6.7 9.1": ["cranio"], "4.8 11.5 22.4": ["jasminoides"], "2.2 13.1 9.4": ["couldcause"], "0.9 5.5 3.2": ["ludorum"], "8.8 6.4 21.4": ["mulatta"], "5.5 1.6 0.7": ["instutitions"], "-3.1 7.1 14.2": ["aremade"], "0.5 18.8 7.8": ["erodable"], "3.9 0.5 5.7": ["pyung"], "-2.4 -0.0 5.7": ["administrateur"], "10.9 -1.0 13.6": ["freetype"], "-0.7 4.3 9.3": ["adaptogenic"], "6.6 3.0 27.1": ["thermostabilized"], "1.6 16.3 12.6": ["postform"], "9.6 4.3 17.3": ["vind"], "21.7 5.5 11.5": ["foglamp"], "3.9 -10.8 1.8": ["lth"], "14.2 7.7 14.7": ["thake"], "0.8 2.8 -8.0": ["sident"], "-4.0 7.1 -1.7": ["actvist"], "6.1 5.0 18.3": ["fortunei"], "6.5 3.6 0.8": ["annuelle"], "1.0 10.4 8.1": ["touchdwon"], "12.7 3.6 18.0": ["sviluppo"], "8.8 12.0 17.7": ["clarkson"], "-7.1 17.6 4.0": ["gade"], "16.6 9.9 13.0": ["snakeoil"], "3.2 6.4 12.7": ["feldman"], "11.9 14.5 3.6": ["mishmashes"], "9.1 9.0 10.1": ["ului"], "-10.0 4.4 15.2": ["pangangailangan"], "5.8 9.1 15.8": ["majus"], "3.1 8.2 -0.0": ["cleavable"], "7.4 -0.9 -7.5": ["nanopharmaceuticals"], "4.6 11.8 12.6": ["compartir"], "11.0 6.1 15.6": ["mene"], "4.8 6.5 20.5": ["medius"], "12.8 2.8 5.4": ["datings"], "9.7 10.2 0.7": ["ntsc"], "-0.8 5.2 2.9": ["cardiocirculatory"], "5.0 7.8 3.8": ["seriou"], "8.1 16.8 2.7": ["auristatin"], "15.4 11.7 11.4": ["eyelinered"], "11.5 9.3 28.7": ["sarap"], "3.9 11.0 6.4": ["photoconversion"], "14.9 6.9 14.1": ["knickerbocker"], "1.5 -1.3 6.7": ["ording"], "9.7 18.9 15.7": ["transmissable"], "2.9 -3.3 10.8": ["saled"], "-1.7 9.5 5.9": ["sawaal"], "-1.1 17.6 9.5": ["historicos"], "14.6 11.6 8.3": ["baryonic"], "7.8 -0.4 8.8": ["recibido"], "14.5 2.7 32.0": ["brandywine"], "10.1 8.7 17.0": ["fragilis"], "7.6 4.4 -1.3": ["miniter"], "10.2 8.2 6.6": ["smartpens"], "5.5 6.9 29.9": ["locovore"], "4.3 4.1 17.4": ["matanda"], "1.4 0.3 12.4": ["aate"], "9.8 25.5 10.3": ["monomaniacally"], "10.8 -0.3 -3.1": ["ltee"], "-0.0 1.7 9.8": ["paracellular"], "10.6 0.4 36.0": ["scamorza"], "-0.3 11.9 5.8": ["countryand"], "8.7 19.0 18.5": ["typhimurium"], "-7.8 12.2 -1.3": ["talaaq"], "3.3 4.8 11.2": ["vaginosis"], "-2.4 0.0 5.3": ["nday"], "-9.6 13.3 2.8": ["orotherwise"], "5.2 8.6 16.2": ["jhoom"], "10.6 4.6 6.7": ["robably"], "4.9 -0.1 -2.7": ["mpi"], "5.7 13.6 7.6": ["interestedly"], "8.4 11.7 -0.5": ["unasserted"], "1.6 5.2 2.2": ["acetyltransferase"], "6.6 -3.7 6.9": ["epoc"], "9.2 -4.0 8.1": ["dagli"], "1.2 -10.0 -1.9": ["highligh"], "-4.9 8.6 2.5": ["brees"], "14.9 16.2 13.8": ["expellers"], "5.9 -2.8 2.1": ["tripleplay"], "-0.8 -1.3 -3.3": ["implementa"], "15.3 8.7 7.2": ["websphere"], "25.7 11.8 27.3": ["waddlers"], "0.9 12.2 5.9": ["servotronic"], "14.5 18.0 -1.0": ["herasat"], "-4.3 13.2 9.5": ["boundaried"], "8.7 -0.9 3.8": ["eligen"], "10.0 -1.5 8.2": ["phlebectomy"], "3.0 19.8 10.6": ["ketuanan"], "18.3 8.3 10.6": ["cardon"], "2.2 -1.9 9.6": ["chwe"], "8.7 3.4 10.6": ["handbike"], "5.2 6.1 14.0": ["poplu"], "10.6 13.9 5.6": ["malvertisements"], "0.7 6.8 2.2": ["contar"], "26.1 10.3 3.4": ["diasaster"], "18.8 15.7 37.3": ["planthoppers"], "14.1 1.6 8.9": ["calcuations"], "3.6 11.6 3.0": ["futurecast"], "-0.8 3.0 2.4": ["capncomics"], "6.1 5.9 9.5": ["eonline"], "3.3 5.6 13.3": ["decantation"], "5.9 7.7 6.2": ["fernandez"], "4.3 1.4 5.1": ["composants"], "11.4 1.3 -6.2": ["agreemnt"], "15.2 14.2 11.3": ["craggily"], "22.5 2.1 9.4": ["sunbleached"], "37.4 5.9 10.5": ["billiondollar"], "15.8 15.9 11.7": ["systray"], "6.6 0.9 4.5": ["vorm"], "17.4 4.6 15.8": ["ugu"], "4.6 9.8 10.6": ["calcic"], "9.4 8.8 30.1": ["floppin"], "14.8 11.1 30.5": ["unhulled"], "12.6 7.1 12.5": ["provincia"], "7.7 6.3 10.8": ["plantaris"], "5.1 2.2 1.6": ["electrochemist"], "7.2 0.2 12.3": ["polyacrylonitrile"], "0.1 8.0 1.8": ["filmfare"], "11.1 8.1 20.2": ["puttylike"], "12.6 10.6 16.9": ["endrin"], "12.9 -2.6 2.4": ["pipeless"], "10.0 8.7 5.1": ["backmark"], "11.0 11.3 12.2": ["viverra"], "6.4 -0.6 11.3": ["gyfer"], "-0.2 4.1 12.3": ["eil"], "-5.4 4.5 2.1": ["ided"], "7.4 5.7 20.8": ["syringa"], "10.6 3.4 8.5": ["tonks"], "-6.3 -1.5 4.7": ["cytogenic"], "5.0 -5.7 -4.1": ["sman"], "5.4 -3.4 4.0": ["ansi"], "4.2 -1.0 5.5": ["actionnaires"], "2.0 -6.7 -0.7": ["ridien"], "2.8 -5.0 10.6": ["ladd"], "9.0 5.1 18.0": ["cuit"], "12.1 -1.6 3.3": ["superstations"], "-5.0 -1.1 3.4": ["gestartet"], "4.5 -1.1 9.9": ["vorbis"], "4.6 9.4 0.9": ["targeter"], "14.8 14.5 7.7": ["opensuse"], "1.3 12.7 13.8": ["traduction"], "-5.4 4.1 6.0": ["undefinitized"], "20.5 6.5 39.1": ["undulatus"], "0.6 -2.5 20.6": ["lorraine"], "7.5 2.9 11.2": ["maille"], "0.1 6.3 4.3": ["lipocalin"], "5.4 13.3 12.5": ["unself"], "1.6 -8.5 3.8": ["hahl"], "-0.2 20.9 12.2": ["baruch"], "11.2 12.4 23.9": ["stellata"], "-1.8 3.4 3.8": ["cinefan"], "-2.6 11.0 2.0": ["firstline"], "3.2 1.9 16.2": ["propuesta"], "16.1 2.6 9.7": ["afix"], "1.1 13.0 16.3": ["jimmie"], "2.4 19.7 9.8": ["iacs"], "5.0 -1.1 -2.9": ["ihaveprettyfeet"], "11.0 12.5 27.6": ["citri"], "2.3 15.2 3.0": ["ventrolateral"], "-1.1 -5.3 -2.6": ["microtec"], "8.6 13.1 10.2": ["dujone"], "7.5 10.0 5.9": ["socialprise", "rnment"], "2.8 3.8 24.7": ["aviculturists"], "6.9 -13.8 19.1": ["duchesse"], "8.7 -3.3 13.2": ["registraton"], "13.1 5.5 14.6": ["opport"], "2.9 5.6 13.1": ["mawala"], "-0.8 15.1 12.0": ["depp"], "4.0 4.2 -1.0": ["encourag"], "8.5 10.7 32.9": ["spikehorn"], "9.2 9.5 13.2": ["stormily"], "11.8 4.9 5.2": ["duhr"], "0.7 2.8 9.6": ["aerobiology"], "4.1 2.7 0.4": ["phenoxy"], "0.3 18.9 13.4": ["areally"], "6.1 -2.5 5.0": ["gedaan"], "21.3 1.3 36.6": ["whiptail"], "-1.8 5.9 7.8": ["lacunar"], "11.7 16.6 17.1": ["chanty"], "4.4 12.0 13.3": ["duha"], "-0.7 2.1 6.5": ["souscription"], "3.7 -2.5 5.4": ["interfaz"], "0.9 13.8 3.2": ["proguanil"], "-2.9 -0.4 18.3": ["aralan"], "9.5 5.1 9.7": ["confiance"], "18.4 18.1 20.8": ["parthenogenic"], "8.2 4.4 0.6": ["mininster"], "9.1 2.9 8.4": ["submental"], "-1.0 15.2 3.9": ["kcr"], "5.8 5.1 3.9": ["postmastectomy"], "-6.1 0.5 1.4": ["rency"], "1.4 8.4 0.0": ["proche"], "6.9 3.4 21.3": ["pulcherrima"], "0.8 5.0 11.4": ["utos"], "13.4 28.9 15.8": ["turneth"], "5.7 3.6 12.2": ["seminole"], "-2.3 -5.0 7.8": ["subglottic"], "5.3 13.5 10.0": ["chitty"], "-2.7 4.5 0.1": ["associa"], "8.2 -8.9 12.3": ["mpr"], "3.5 11.4 8.9": ["wyndstorm"], "9.8 2.7 10.9": ["kunt"], "11.4 25.5 18.7": ["infestans"], "9.4 3.8 -5.0": ["bmd"], "9.8 11.0 15.8": ["foulbrood"], "-6.1 1.4 15.5": ["titingnan"], "4.8 7.0 26.3": ["patatas"], "11.4 5.6 12.4": ["hathaway"], "5.2 21.6 13.3": ["culturism"], "26.1 10.7 20.8": ["bipedally"], "18.4 11.4 -1.7": ["cyberactivist"], "8.5 3.4 11.1": ["vingt"], "11.4 1.3 1.2": ["engi"], "4.2 5.4 13.3": ["ricerca"], "12.5 -7.3 -1.5": ["overeenkomst"], "2.3 7.5 9.4": ["jfb"], "7.0 2.8 14.0": ["dyfodol"], "-0.7 8.2 21.5": ["mainit"], "5.1 -0.0 1.4": ["ligating"], "2.3 5.6 9.9": ["histrelin"], "9.5 21.2 14.3": ["backfist"], "10.5 16.7 14.3": ["toxoids"], "4.7 4.3 18.5": ["tuku"], "13.2 -11.4 16.6": ["bahs"], "3.9 19.3 3.2": ["unwept"], "-4.5 10.7 10.7": ["dahan"], "20.4 16.7 14.9": ["owlishly"], "0.2 0.1 11.7": ["cytotec"], "2.8 3.5 9.1": ["conivaptan"], "13.3 7.1 27.2": ["winterizer"], "-6.9 -10.6 5.0": ["halloffame"], "4.6 14.6 21.3": ["betide"], "9.7 3.6 12.3": ["luxation"], "13.3 -8.3 -1.0": ["telemed"], "-2.1 19.1 15.4": ["upcard"], "8.2 11.5 11.3": ["cruzi"], "8.1 2.4 9.5": ["chemoprotective"], "12.0 6.2 11.8": ["sult"], "9.6 3.4 21.2": ["tential"], "-9.8 4.0 8.6": ["bailbond"], "15.0 3.4 11.6": ["refinable"], "5.4 -2.4 -0.0": ["xmlns"], "1.5 7.6 10.2": ["aortoiliac"], "6.8 15.8 5.3": ["mahaan"], "17.1 11.7 30.3": ["lechwe"], "6.1 4.9 7.3": ["kafala"], "9.1 13.4 15.2": ["tortor"], "6.4 6.3 20.2": ["brimless"], "18.0 0.6 24.6": ["superba"], "8.2 10.3 3.4": ["drugable"], "15.0 17.4 -3.3": ["hactivist"], "1.5 23.2 -1.0": ["genociders"], "12.4 6.5 24.3": ["smartshops"], "8.3 5.1 15.8": ["byw"], "5.2 2.0 17.8": ["headage"], "7.0 2.2 3.6": ["emory"], "1.2 -2.6 13.6": ["francisco"], "-2.2 6.7 6.6": ["fibrocystic"], "1.1 -3.2 5.1": ["demandes"], "-1.1 -2.5 -1.6": ["pulmonic"], "20.7 1.8 21.4": ["nongrocery"], "5.3 12.6 13.3": ["backcut"], "10.1 7.6 17.4": ["potong"], "10.2 4.9 9.5": ["besoins"], "14.3 6.2 14.1": ["bromantan"], "-6.0 6.5 4.0": ["honorman"], "11.4 3.3 11.5": ["versienummer"], "11.7 13.9 2.3": ["emissons"], "12.3 9.4 10.9": ["hydrostatically"], "8.1 10.4 15.1": ["collin"], "9.8 5.2 -2.4": ["avia"], "4.1 -12.1 3.3": ["conferenza"], "17.1 19.1 15.8": ["earthers"], "3.7 6.9 21.4": ["wika"], "9.5 4.2 8.6": ["defoaming"], "15.6 4.1 11.6": ["niin"], "12.0 12.6 15.5": ["dicount"], "-5.6 13.3 -7.0": ["efense"], "13.2 16.2 0.1": ["stuxnet"], "-5.0 16.3 3.6": ["indivi"], "10.2 19.0 9.8": ["terrorismo"], "-10.9 -1.4 -3.2": ["hyperreflexia"], "-1.1 11.1 8.6": ["inko"], "3.6 10.5 5.8": ["partylists"], "-0.1 3.8 22.6": ["carnaroli"], "8.9 0.7 12.5": ["politan"], "5.9 6.0 9.3": ["viser"], "8.4 -2.1 12.4": ["psykter"], "6.3 11.7 13.4": ["thiosulphate"], "2.4 0.4 19.2": ["consommateurs"], "9.9 25.0 11.5": ["grindfest"], "12.4 9.8 11.1": ["stellate"], "0.3 -0.1 1.6": ["organosilicon"], "8.3 15.2 13.4": ["gunmaking"], "-3.8 -6.7 -6.5": ["edical"], "13.9 8.1 13.8": ["morphometrics"], "2.1 -3.3 9.1": ["contribu"], "-0.1 4.5 10.2": ["utha"], "7.3 -6.4 8.4": ["ennill"], "3.3 8.0 16.4": ["suportahan"], "14.0 10.5 9.3": ["tipos"], "3.5 3.1 10.6": ["pehla"], "10.3 0.2 14.2": ["yvonne"], "17.0 3.9 13.2": ["woogie"], "2.9 8.3 10.4": ["matrimonies"], "0.9 1.9 9.0": ["glulisine"], "4.7 6.6 -0.4": ["turbaning"], "2.6 9.0 10.9": ["jale"], "0.5 6.4 7.8": ["relativement"], "3.2 18.0 11.5": ["lymphotoxin"], "6.2 9.2 6.2": ["ultraconfident"], "6.8 4.1 15.4": ["scribers"], "8.1 4.0 7.6": ["prosti"], "13.1 11.4 33.3": ["olallieberry"], "4.5 2.7 12.5": ["uwishunu"], "-1.4 7.8 4.9": ["iisa"], "2.5 6.1 6.8": ["knoc"], "6.9 1.1 22.4": ["dolman"], "7.8 6.0 6.8": ["duple"], "8.5 2.3 11.4": ["gobar"], "5.8 6.0 21.1": ["beachboy"], "17.8 10.3 23.5": ["sharkfin"], "17.9 4.4 -0.8": ["edaily"], "12.1 13.6 10.1": ["playsheet"], "10.8 13.4 18.3": ["slurvy"], "1.3 -0.4 -8.0": ["cardiography"], "-7.8 -5.6 1.4": ["iddat"], "-1.9 3.1 6.1": ["monthsended"], "9.5 10.2 34.1": ["whaleship"], "4.6 -5.0 9.3": ["gih"], "5.4 7.5 10.8": ["reaccommodation"], "18.8 15.3 10.5": ["thumbers"], "5.5 11.7 6.9": ["greatgreat"], "4.2 0.5 8.7": ["dermaceutical"], "5.0 8.4 14.6": ["maliit"], "6.0 4.9 20.1": ["ylg"], "2.4 -6.0 10.2": ["hydroxymethyl"], "-1.5 -1.7 11.2": ["tercer"], "-5.3 4.5 0.7": ["milenge"], "6.8 10.9 7.6": ["somme"], "4.8 11.7 14.7": ["adlaw"], "19.2 4.3 14.8": ["nonchocolate"], "4.6 15.8 21.7": ["flatbottom"], "9.9 -0.2 6.5": ["contrato"], "1.0 6.5 14.7": ["solusyon"], "6.0 0.8 14.9": ["myotonic"], "16.8 -4.6 6.4": ["azienda"], "18.8 10.8 27.1": ["piff"], "8.0 -8.3 9.4": ["fahn"], "12.6 -1.3 23.4": ["kachi"], "-1.2 -2.0 3.8": ["prelicense"], "10.6 8.3 11.7": ["firmographics"], "-2.6 22.1 20.0": ["habitated"], "-8.1 -2.3 1.5": ["addictionologist"], "7.8 9.4 11.0": ["pelle"], "-2.3 0.6 2.4": ["rences"], "1.1 -4.6 6.7": ["vicepresidente"], "9.1 11.4 27.5": ["decapod"], "1.0 13.5 12.2": ["preemergent"], "2.5 4.7 11.0": ["intracortical"], "10.3 20.9 10.0": ["wunnerful"], "5.0 -2.8 11.0": ["plete"], "-1.8 -0.5 8.6": ["longus"], "6.4 10.6 13.2": ["beur"], "6.3 11.4 12.7": ["euismod"], "6.4 10.4 6.9": ["onenote"], "2.3 -2.8 -2.7": ["ptions"], "-0.3 11.0 1.0": ["adrenoreceptor"], "5.0 -3.7 6.4": ["fown"], "-3.5 -7.8 1.5": ["overnor"], "5.5 -4.9 11.5": ["olympia"], "12.2 19.5 9.8": ["hoku"], "6.7 14.3 9.8": ["gummit"], "-6.3 8.8 4.4": ["influenzae"], "11.4 1.2 13.1": ["ramas"], "2.0 8.4 11.5": ["intercambio"], "9.5 4.8 6.2": ["offuture"], "15.3 0.4 15.5": ["biere"], "13.1 19.6 15.1": ["scalene"], "-2.7 0.1 -3.4": ["perflutren"], "4.6 -6.5 9.6": ["qsr"], "4.9 5.2 -9.1": ["vised"], "0.9 1.3 11.5": ["pangunahing"], "-1.4 3.4 2.3": ["mevalonate"], "6.8 19.6 9.1": ["foehn"], "11.5 10.5 13.9": ["terday"], "-0.1 2.7 5.5": ["steroidogenic"], "5.6 -5.3 5.6": ["garza"], "11.7 10.7 16.0": ["towheads"], "7.3 -3.9 2.2": ["fournisseurs"], "13.0 19.1 21.1": ["kapit"], "-3.4 15.1 6.1": ["unbailable"], "7.3 12.9 34.4": ["solunar"], "16.6 1.0 7.3": ["zens"], "-2.3 -1.6 2.6": ["norelgestromin"], "-1.2 -4.8 8.9": ["ahf"], "12.0 0.3 7.7": ["furbishing"], "2.2 16.5 3.5": ["solatia"], "-5.8 5.4 0.7": ["setzen"], "11.3 5.1 6.5": ["laten"], "25.3 10.9 16.7": ["scritch"], "10.4 12.5 3.7": ["contextless"], "0.7 5.6 0.6": ["liab"], "16.5 9.2 2.6": ["throned"], "10.8 14.8 22.6": ["downey"], "9.7 10.4 10.7": ["grrls"], "18.3 10.8 5.6": ["sacrifical"], "4.2 5.7 9.5": ["juez"], "11.2 11.8 20.3": ["personnage"], "2.7 32.0 -0.3": ["islamo"], "18.4 7.3 15.7": ["affenpinscher"], "9.1 8.6 7.6": ["clothers"], "11.6 5.0 2.1": ["sofoles"], "6.5 8.5 18.3": ["sulfosalts"], "2.2 -0.6 6.4": ["attrac"], "-1.6 2.5 9.6": ["labi"], "6.3 8.1 10.6": ["jcs"], "14.0 8.7 21.4": ["hambre"], "17.9 10.6 45.2": ["papillote"], "1.8 15.4 14.3": ["chromated"], "14.7 16.5 1.1": ["wagen"], "1.4 5.3 11.6": ["venga"], "3.5 0.9 4.3": ["iglesia"], "-4.7 1.4 15.8": ["debridements"], "6.5 1.9 12.9": ["lograr"], "6.9 5.8 10.3": ["depakote"], "17.9 12.2 21.1": ["graving"], "3.2 1.5 3.3": ["dichloroethene"], "-3.2 -3.3 11.2": ["erformance"], "14.2 25.1 7.7": ["hoistway"], "9.6 8.8 17.8": ["serpentinized"], "2.9 4.6 10.5": ["microangiopathy"], "-0.1 15.2 15.3": ["undisplaced"], "11.6 9.1 17.3": ["gaiting"], "7.0 4.1 9.8": ["pixy"], "13.8 7.5 0.7": ["magno"], "8.0 4.2 6.1": ["zowel"], "13.5 5.4 32.7": ["duxelle"], "11.8 16.3 24.1": ["assery"], "18.3 8.4 8.7": ["notcher"], "5.5 10.0 3.9": ["frontoparietal"], "11.7 12.9 11.9": ["termism"], "2.9 14.9 8.3": ["harmer"], "15.7 8.7 24.7": ["oikomi"], "-0.7 5.5 11.0": ["myoepithelial"], "-4.0 12.3 -0.6": ["heand"], "16.9 4.4 13.3": ["nappings"], "9.4 4.5 7.6": ["sonido"], "-4.5 8.4 9.2": ["sewaks"], "12.1 2.8 17.1": ["backways"], "3.6 10.3 3.0": ["villus"], "-6.4 16.7 1.3": ["deeni"], "1.7 3.5 6.8": ["glyceryl"], "4.4 2.2 5.6": ["tmnet"], "6.6 17.8 8.6": ["pillarbox"], "-5.3 11.0 7.5": ["reza"], "12.2 2.9 13.4": ["magasins"], "3.3 0.5 11.2": ["industriya"], "17.4 0.5 3.9": ["killowatt"], "-2.1 5.3 13.7": ["guanylate"], "6.0 11.8 3.9": ["unlooted"], "5.7 4.6 11.0": ["sesquiterpene"], "-1.2 2.1 13.4": ["vois"], "4.6 7.4 5.8": ["unshown"], "-1.3 4.9 4.4": ["adop"], "1.4 12.8 16.5": ["pipiens"], "3.5 5.6 2.8": ["photoactivated"], "-2.1 -6.9 10.4": ["offnet"], "12.3 9.4 15.6": ["conser"], "7.4 8.7 6.5": ["modernes"], "5.7 9.2 11.9": ["faisant"], "17.4 9.3 20.8": ["armspan"], "-3.5 1.3 1.9": ["execut"], "-0.9 9.3 7.1": ["bendroflumethiazide"], "-0.5 -7.4 9.1": ["toria"], "6.3 6.5 19.2": ["stockinette"], "9.5 10.9 2.0": ["disqus"], "6.1 2.0 5.1": ["sellng"], "-1.1 -7.3 -1.6": ["polytechnique"], "4.7 0.2 7.9": ["subdivisons"], "6.9 2.2 17.1": ["vong"], "-3.0 4.3 3.2": ["unica"], "0.7 2.7 1.6": ["glatiramer"], "8.3 -9.8 1.5": ["pedorthic"], "10.7 -13.9 -3.7": ["rejoint"], "-7.6 1.6 3.5": ["worktexts"], "0.0 2.6 0.1": ["uniformities"], "2.4 -2.2 -0.8": ["eiro"], "7.3 2.3 22.5": ["finner"], "7.0 -2.1 5.2": ["mrindependent"], "15.9 28.2 6.8": ["hobnailed"], "6.3 -7.0 0.6": ["rebrandable"], "-6.4 0.6 16.4": ["miyembro"], "0.7 4.9 10.2": ["imperfecta"], "8.0 -0.3 3.2": ["usine"], "0.2 -11.8 2.0": ["nuhn"], "13.0 14.7 16.3": ["sluggin"], "7.7 6.5 9.8": ["booky"], "15.8 5.1 6.6": ["vibrometer"], "9.2 11.6 17.5": ["instituciones"], "-7.2 7.6 12.7": ["exotoxin"], "21.4 8.6 10.9": ["drumlike"], "14.7 3.2 -10.0": ["sepago"], "17.1 2.0 8.1": ["shampooers"], "4.7 6.4 6.3": ["teletrack"], "3.7 16.4 20.9": ["depigmented"], "4.7 8.9 12.5": ["rahen"], "11.3 13.9 16.9": ["fusil"], "0.7 -2.7 8.9": ["kwuh"], "7.6 3.0 12.3": ["playslip"], "8.0 2.6 0.9": ["infusible"], "6.0 -1.6 11.3": ["byoo"], "15.0 0.8 7.8": ["krones"], "0.5 0.1 1.4": ["nephrectomies"], "2.2 14.1 14.8": ["finley"], "2.0 7.7 12.7": ["esfuerzo"], "15.3 14.4 27.2": ["woodfired"], "1.4 6.4 3.0": ["forwardable"], "13.7 9.3 4.1": ["ainst"], "1.1 23.4 7.0": ["desync"], "11.9 15.9 9.5": ["interparticle"], "8.1 12.3 14.7": ["boughten"], "3.9 13.0 6.3": ["charterholder"], "7.4 8.8 17.4": ["karangalan"], "-5.9 -5.9 3.4": ["ecting"], "7.3 14.2 18.8": ["mostrar"], "5.8 1.2 3.0": ["prepara"], "5.1 -3.0 15.5": ["digwydd"], "12.5 -2.1 7.1": ["aden"], "2.5 3.3 11.2": ["siguiente"], "7.9 9.2 6.7": ["easyedge"], "-2.7 -9.8 2.9": ["cantly"], "8.1 4.5 8.8": ["underdrive"], "2.1 6.1 11.9": ["traffi"], "-0.5 33.5 -0.7": ["momineen"], "-3.7 20.5 13.1": ["skel"], "0.7 5.6 3.7": ["audion"], "2.6 -1.4 2.6": ["mppa"], "7.7 -2.7 17.1": ["postes"], "-0.1 1.2 -1.0": ["preleague"], "4.2 2.0 6.3": ["ringitt"], "15.1 8.5 29.2": ["nacreous"], "13.4 16.9 24.9": ["muriqui"], "8.9 6.4 15.9": ["dispositivo"], "9.0 12.0 3.5": ["hocus"], "15.7 3.0 21.6": ["leotarded"], "8.2 6.0 13.0": ["lanzamiento"], "4.8 9.1 3.0": ["dispositifs"], "11.9 13.0 11.2": ["samantharonson"], "11.3 -0.3 11.0": ["sprin"], "6.3 9.0 19.8": ["yahs"], "17.7 6.4 18.0": ["bowfront"], "0.8 7.7 17.9": ["twds"], "11.6 9.0 13.2": ["carpel"], "8.6 8.3 15.1": ["cyromazine"], "2.1 2.7 -1.3": ["patronship"], "7.6 7.5 20.7": ["willowleaf"], "20.9 19.1 26.5": ["parasailer"], "4.0 -2.1 13.1": ["accretionary"], "11.1 10.7 17.4": ["jua"], "11.3 15.6 5.5": ["grises"], "4.5 13.8 -1.8": ["amerikanischen"], "6.7 4.5 15.1": ["propertly"], "4.4 3.4 7.3": ["sexto"], "10.7 3.1 10.4": ["multipin"], "2.9 13.0 10.6": ["cannonbone"], "8.3 17.4 12.9": ["swayable"], "-3.8 6.0 0.5": ["nonobstructive"], "2.1 9.7 13.5": ["kaffiyah"], "15.4 16.2 27.0": ["trogon"], "-0.1 22.2 0.8": ["nuclearize"], "13.0 9.3 7.7": ["negocios"], "4.9 2.6 6.0": ["abuso"], "12.8 6.4 22.1": ["coastward"], "9.2 9.7 12.8": ["quello"], "10.2 4.7 4.3": ["patho"], "5.9 1.3 4.1": ["gration"], "11.3 7.5 5.8": ["hematopoetic"], "3.9 17.0 8.4": ["phathi"], "3.2 9.9 7.7": ["bulemia"], "1.9 13.7 9.0": ["paratyphoid"], "0.7 7.8 12.9": ["zonas"], "8.1 5.8 25.8": ["antici"], "2.3 0.0 2.6": ["architectes"], "14.2 16.9 29.3": ["trysail"], "-1.9 13.9 6.4": ["obp"], "11.5 4.0 15.8": ["boisei"], "9.4 -2.8 6.0": ["autosurf"], "-0.0 12.7 -0.8": ["distribut"], "9.2 -1.3 5.6": ["prossimo"], "11.9 11.3 14.2": ["consommation"], "-3.0 7.3 -6.1": ["ismail"], "-2.8 -0.3 19.8": ["mema"], "-8.9 11.7 -4.2": ["vidence"], "8.1 6.3 7.0": ["summiter"], "9.2 -1.7 9.6": ["exceutive"], "13.5 11.0 15.1": ["reunifies"], "19.4 5.8 19.7": ["gling"], "19.5 -1.1 12.4": ["fullsized"], "18.5 12.4 8.5": ["clickity"], "7.8 1.8 5.2": ["hurch"], "19.1 7.0 13.9": ["lookey"], "11.9 2.7 12.8": ["ribboncutting"], "11.0 0.2 8.2": ["lactam"], "1.0 -0.2 12.7": ["posttranslational"], "-1.5 11.2 -4.1": ["notam"], "8.3 -3.9 1.0": ["arrondisement"], "10.6 4.4 19.6": ["piao"], "13.1 8.7 23.6": ["nonlead"], "10.4 4.8 9.9": ["demethylating"], "16.3 4.8 34.5": ["snelled"], "3.0 6.4 6.3": ["wobei"], "2.9 -1.4 6.8": ["niveaux"], "16.9 23.0 19.6": ["mandrakes"], "11.5 5.1 9.0": ["amoun"], "13.8 1.0 7.5": ["symbole"], "15.1 9.3 12.1": ["ambu"], "-3.8 14.9 7.7": ["dimittis"], "11.7 6.0 4.3": ["voitures"], "2.1 -0.1 7.0": ["parolable"], "8.3 5.4 4.0": ["toolpusher"], "-5.1 -4.1 -2.4": ["istrict"], "8.9 12.1 8.9": ["fahrv"], "5.5 8.8 14.2": ["jullie"], "-3.3 -16.5 -2.6": ["erated"], "11.2 7.6 13.3": ["boylesque"], "-6.8 -5.4 -8.3": ["timate"], "1.8 23.2 6.1": ["laceratingly"], "7.3 -3.8 5.7": ["richter"], "14.4 15.7 17.6": ["squeakquel"], "15.8 5.2 36.4": ["tonkotsu"], "6.1 9.7 27.7": ["orgeat"], "-5.9 -0.0 4.5": ["cycloserine"], "12.0 8.7 6.2": ["styn"], "22.4 12.8 14.6": ["continential"], "5.0 16.4 10.2": ["unsimilar"], "9.9 -1.3 3.2": ["explor"], "4.0 1.3 5.2": ["maladie"], "-3.7 4.6 7.2": ["echinocandin"], "-2.3 2.4 17.6": ["ituloy"], "1.3 5.2 3.5": ["nues"], "-2.5 7.9 7.5": ["enced"], "9.4 6.5 -8.6": ["toughbook"], "2.8 13.8 8.0": ["mammographically"], "15.8 1.4 7.7": ["kewpie"], "8.4 -2.0 2.0": ["ntry"], "9.6 20.1 9.9": ["polloi"], "-3.0 8.4 1.6": ["ctors"], "5.6 5.3 0.6": ["erreichen"], "5.4 5.8 -2.2": ["exeutive"], "12.9 7.7 21.0": ["osage"], "10.8 18.9 14.8": ["madcow"], "1.9 0.6 7.3": ["sternoclavicular"], "10.9 10.6 31.6": ["bulghur"], "-2.7 -2.1 12.4": ["leroy"], "3.1 17.5 13.2": ["delicto"], "-1.6 -6.1 2.4": ["nanomoles"], "1.1 -1.0 11.8": ["mcfg"], "4.5 -4.2 6.9": ["cians"], "16.0 15.4 17.6": ["kune"], "6.0 15.1 4.0": ["ocrats"], "9.0 1.4 5.9": ["humanos"], "2.6 11.0 6.4": ["nonbankruptcy"], "16.1 9.2 7.1": ["sideview"], "-2.1 4.3 6.2": ["aggregometry"], "-5.2 13.3 -2.6": ["uninominal"], "4.8 9.9 8.9": ["tritiated"], "7.6 -4.4 12.2": ["ricavi"], "-1.0 0.0 2.6": ["coetibus"], "-0.3 0.7 10.3": ["particulares"], "0.9 -7.5 4.1": ["fortifiers"], "6.7 9.5 8.3": ["essentiel"], "6.1 4.5 11.3": ["spermatic"], "14.2 8.5 10.2": ["cholestorol"], "5.3 1.4 8.3": ["brompheniramine"], "10.9 2.4 9.8": ["digestors"], "9.1 -1.8 12.4": ["triacetate"], "16.7 5.8 12.1": ["dohr"], "7.8 11.1 5.3": ["intesified"], "-0.4 11.4 13.2": ["obair"], "-1.3 -3.4 12.1": ["achiev"], "10.2 -3.7 7.4": ["clonings"], "1.9 -3.1 2.5": ["ficient"], "5.3 -1.3 9.6": ["consola"], "10.1 10.3 16.6": ["epitaxially"], "13.3 -0.4 5.0": ["koop"], "6.8 12.4 7.2": ["ciety"], "0.3 -3.7 3.6": ["octubre"], "3.6 -0.4 11.7": ["iho"], "-0.3 9.3 6.2": ["mamta"], "19.2 15.4 14.9": ["putzing"], "4.4 2.0 -0.7": ["preparticipation"], "6.2 -4.1 4.2": ["nello"], "3.4 21.6 6.6": ["bhaktas"], "10.7 12.8 26.6": ["frogmouth"], "3.5 9.9 12.1": ["eccrine"], "1.8 8.0 3.5": ["tribromoanisole"], "6.9 15.0 14.0": ["nominaton"], "3.7 17.7 14.2": ["ladai"], "9.4 2.9 7.9": ["licenza"], "-4.1 2.7 9.5": ["previ"], "12.7 16.1 29.6": ["potoroo"], "-2.9 8.6 6.8": ["nonfelony"], "5.0 6.0 7.6": ["acknow"], "24.0 21.5 10.2": ["vivisectionist"], "-4.9 5.5 6.5": ["emocratic"], "12.0 7.4 7.9": ["creo"], "10.3 11.0 14.0": ["dekhna"], "7.6 0.7 17.7": ["showshoe"], "20.3 -1.9 7.9": ["videosharing"], "10.6 -4.2 13.8": ["urbana"], "-2.8 3.9 -2.4": ["primum"], "5.1 3.2 -3.0": ["asola"], "3.0 -2.0 2.6": ["alty"], "-0.8 7.2 17.0": ["pumapasok"], "14.1 14.9 12.2": ["aluta"], "10.2 9.6 2.4": ["webblog"], "-5.0 7.5 10.7": ["fein"], "7.7 9.7 12.5": ["agonal"], "12.8 7.3 22.1": ["arrowwood"], "17.5 -2.2 2.6": ["overname"], "1.2 4.3 16.0": ["velous"], "16.3 17.1 10.8": ["chetan"], "10.1 8.8 2.7": ["oilgate"], "5.4 9.9 -0.5": ["errores"], "4.2 10.2 13.6": ["wella"], "15.0 3.6 35.4": ["inasal"], "4.5 21.3 11.6": ["kutte"], "-3.4 -1.5 -1.2": ["charterholders"], "7.2 -0.1 19.7": ["discretionaries"], "16.7 23.2 11.9": ["thead"], "12.1 2.8 9.9": ["flate"], "-4.2 2.6 6.8": ["nonproliferative"], "10.6 -6.4 26.4": ["lumpiang"], "2.8 2.0 -1.3": ["bioconjugation"], "14.7 5.8 17.6": ["snowfence"], "4.4 21.6 12.9": ["wouldst"], "6.5 1.1 -3.1": ["netware"], "0.8 7.1 15.4": ["affluently"], "-3.0 -8.7 -2.2": ["plications"], "8.6 19.8 9.8": ["ckers"], "6.5 1.4 12.6": ["ffect"], "6.6 20.4 -3.5": ["wholy"], "6.3 5.8 11.2": ["origi"], "4.1 4.2 3.4": ["eresource"], "8.7 5.0 14.6": ["nephrosis"], "1.2 11.6 12.0": ["pyrimidines"], "6.7 10.2 21.2": ["appetit"], "1.3 2.9 12.4": ["kelli"], "7.9 -0.7 3.6": ["tendinits"], "5.6 -0.4 -1.6": ["protocole"], "2.7 20.0 9.0": ["tributing"], "6.9 8.9 1.8": ["fourier"], "1.0 7.6 10.5": ["curso"], "12.2 8.3 11.0": ["jager"], "6.8 -1.7 16.9": ["sorbate"], "17.9 10.1 34.2": ["shimeji"], "13.5 7.9 8.9": ["instru"], "-2.6 12.9 -3.9": ["fidelis"], "11.5 0.3 21.9": ["buffings"], "-0.3 6.7 4.9": ["temporoparietal"], "23.7 18.3 27.5": ["rosbifs"], "0.2 8.2 13.8": ["mmad"], "14.3 -2.2 13.8": ["hatmaking"], "7.9 26.9 8.0": ["reoccupies"], "5.6 8.9 24.3": ["hyperpigmented"], "4.3 9.9 14.3": ["shoop"], "-4.3 0.2 9.7": ["dudley"], "7.9 16.4 19.4": ["siha"], "3.6 10.7 12.3": ["diable"], "9.0 5.5 30.2": ["demerara"], "8.2 17.4 18.7": ["vomitoria"], "15.5 13.0 29.8": ["gohan"], "0.3 0.6 -2.1": ["indicat"], "17.9 13.3 21.2": ["micaceous"], "3.8 6.6 7.1": ["apn"], "7.6 8.9 13.1": ["antiflu"], "9.3 9.3 11.1": ["kickboxes"], "11.2 4.7 9.2": ["crescita"], "1.5 6.7 7.9": ["crecimiento"], "10.7 10.0 18.8": ["spokesbird"], "5.3 3.2 7.3": ["investissements"], "-4.0 6.7 10.7": ["makakatulong"], "3.3 23.4 10.3": ["loya"], "6.5 -1.5 1.1": ["lising"], "-1.0 8.0 7.6": ["impormasyon"], "-8.2 3.4 7.3": ["harrisburg"], "0.3 15.8 -0.3": ["sprach"], "8.0 0.5 -1.7": ["bdr"], "8.7 1.5 7.0": ["orchester"], "7.4 8.2 13.9": ["cualquiera"], "9.3 7.1 18.4": ["ruf"], "10.2 9.0 20.7": ["cornuta"], "1.9 7.5 3.0": ["antireflux"], "12.3 1.9 6.9": ["origen"], "-3.4 -10.2 5.8": ["phia"], "-4.3 -2.9 2.8": ["bortner"], "-1.4 7.1 12.1": ["nks"], "12.4 5.9 22.0": ["maska"], "10.4 11.8 6.9": ["lolterizt"], "15.9 -0.6 39.8": ["fritto"], "8.1 7.7 8.2": ["greenschist"], "14.3 0.8 11.4": ["ashtadhatu"], "6.0 9.9 16.8": ["napier"], "-0.4 -2.1 25.5": ["piatti"], "-0.2 -6.7 -0.4": ["dosimetrist"], "9.2 6.4 22.0": ["bunchers"], "15.7 9.9 12.3": ["staidly"], "11.4 7.6 7.6": ["facturing"], "14.4 6.4 4.6": ["antinausea"], "2.1 10.9 5.0": ["nonforfeitable"], "8.9 3.9 1.9": ["syk"], "7.3 6.8 24.0": ["campur"], "-2.9 1.2 -5.7": ["annulation"], "7.0 2.3 10.7": ["toge"], "14.1 12.9 21.1": ["whipsnake"], "5.9 -0.7 0.3": ["intraveneous"], "7.3 9.7 2.6": ["spectroradiometers"], "18.7 6.1 16.5": ["sexta"], "11.2 15.5 10.3": ["scuse"], "11.8 2.5 10.0": ["bitumens"], "-3.9 -0.5 4.5": ["pulsatility"], "-2.1 -7.5 2.5": ["placetype"], "7.1 12.4 15.9": ["thun"], "14.2 6.0 5.3": ["intravital"], "11.4 4.4 25.5": ["asadero"], "7.0 3.1 11.8": ["polyaxial"], "4.5 4.1 7.5": ["deoxyglucose"], "0.7 6.0 13.2": ["sahl"], "-2.1 -2.7 0.7": ["corticotropin"], "3.4 -2.9 6.2": ["lpga"], "-2.5 1.9 0.4": ["faim"], "13.0 15.2 14.4": ["rotundus"], "-0.1 7.5 12.4": ["makatulong"], "0.7 12.4 10.7": ["mycotic"], "11.0 7.3 3.2": ["internatio"], "5.7 5.0 5.7": ["palmprints"], "8.6 11.1 13.4": ["espe"], "5.1 14.7 14.0": ["lectus"], "-5.4 4.6 13.4": ["tanungin"], "7.8 15.7 9.1": ["precipitious"], "10.3 10.7 10.8": ["akshay"], "-3.0 -4.6 -0.2": ["twentyone"], "3.6 2.9 11.4": ["andmarkets"], "4.5 6.0 5.2": ["counterveiling"], "14.4 14.5 17.2": ["echosounder"], "0.7 13.0 11.6": ["extracolonic"], "7.4 -1.8 11.9": ["wheelage"], "1.1 11.7 11.4": ["wrongway"], "1.6 -9.7 9.2": ["aziende"], "3.2 -4.4 -1.7": ["endomicroscopy"], "-0.4 7.4 12.5": ["kapangyarihan"], "7.0 3.4 8.6": ["beneficios"], "-3.8 9.2 2.6": ["nonidentical"], "-10.0 -1.7 -5.6": ["nonbeneficial"], "1.6 10.4 18.4": ["myles"], "7.6 10.0 5.1": ["shuttin"], "27.0 17.6 28.0": ["ursus"], "10.1 -5.7 10.9": ["puhl"], "4.6 2.6 9.2": ["taux"], "12.8 23.1 15.1": ["bitted"], "7.6 3.5 9.7": ["perros"], "-4.1 5.4 0.3": ["ruption"], "2.5 1.0 1.8": ["gement"], "1.7 8.3 -5.3": ["deutscher"], "8.9 -0.3 18.0": ["unemploment"], "-4.4 7.6 11.5": ["oligodeoxynucleotide"], "2.3 5.9 7.9": ["biopreservation"], "2.2 10.1 12.8": ["hayley"], "10.9 5.2 22.8": ["mycelial"], "6.3 1.0 10.3": ["rekordbox"], "15.5 6.1 16.4": ["foreheaded"], "6.7 3.4 6.2": ["excellance"], "32.1 10.9 18.1": ["armillary"], "8.3 2.8 6.5": ["slackware"], "9.7 4.6 14.1": ["stesso"], "2.9 8.2 -4.6": ["nachdem"], "2.5 3.2 10.6": ["micromol"], "2.5 -2.4 9.5": ["pment"], "6.6 9.1 27.4": ["olelo"], "7.5 9.7 18.4": ["nhac"], "-3.4 0.4 3.1": ["titratable"], "-1.4 3.7 -0.9": ["tratamiento"], "-2.3 2.1 2.5": ["nonperformer"], "17.3 0.6 19.7": ["nondiet"], "5.9 13.4 10.2": ["citydwellers"], "-1.0 -3.6 5.4": ["intratumoural"], "17.4 24.4 19.5": ["repellence"], "2.5 8.4 13.1": ["sapu"], "17.1 7.1 6.6": ["wooshing"], "-1.7 10.3 1.0": ["ukr"], "21.5 7.8 24.1": ["hoppity"], "13.2 20.4 20.0": ["plumpy"], "-1.1 2.1 18.3": ["plantarum"], "-6.8 3.0 10.8": ["onya"], "2.8 -4.7 29.1": ["bufala"], "2.8 4.4 8.6": ["etition"], "-4.8 2.9 4.5": ["decremental"], "2.3 6.9 14.7": ["atdhe"], "2.6 8.4 6.1": ["tholeiitic"], "3.6 9.3 13.4": ["jects"], "2.7 -4.7 9.4": ["lative"], "2.4 9.7 3.1": ["grata"], "14.7 -1.0 9.4": ["grootste"], "5.9 9.0 2.6": ["antibiofilm"], "-1.8 6.6 2.8": ["vinod"], "3.6 7.6 -2.0": ["rmvb"], "-2.4 -4.0 8.0": ["roscovitine"], "7.6 12.1 12.5": ["baaki"], "11.8 4.1 19.9": ["gered"], "7.4 8.7 7.4": ["vidi"], "10.2 2.5 8.8": ["sterlings"], "3.6 -0.4 12.7": ["hhw"], "1.9 3.0 0.1": ["essais"], "15.7 15.3 33.3": ["slaty"], "2.7 7.6 6.9": ["windball"], "15.2 15.3 15.4": ["toecaps"], "-0.3 2.9 -3.2": ["prebreathe"], "2.1 15.1 14.3": ["atake"], "2.1 6.6 16.5": ["mataas"], "15.0 7.1 10.1": ["hydroenergy"], "8.4 -6.0 11.3": ["dollari"], "-1.1 4.2 -2.6": ["pepducin"], "-3.1 3.3 2.6": ["nutlin"], "1.9 -2.0 12.3": ["gweithio"], "0.0 12.1 10.2": ["administ"], "10.3 -3.4 16.1": ["bluefusion"], "11.6 3.4 16.7": ["frou"], "-2.2 3.4 -3.2": ["rld"], "7.8 2.5 -4.5": ["stentless"], "7.6 10.8 24.5": ["aati"], "7.7 2.6 8.6": ["reflowing"], "-1.3 2.6 20.0": ["organotin"], "9.0 4.7 9.8": ["comprare"], "-4.0 10.9 1.0": ["ayesha"], "3.9 10.1 6.0": ["trente"], "2.9 -2.9 13.7": ["galw"], "-3.3 -1.0 4.3": ["histori"], "14.0 7.1 8.8": ["jumplist"], "2.1 5.3 13.7": ["escuelas"], "9.2 11.6 17.9": ["litargirio"], "0.4 -8.6 6.5": ["pahn"], "18.2 13.8 18.9": ["meshy"], "8.7 -1.7 5.8": ["americanidol"], "3.9 7.2 6.7": ["mecasermin"], "-6.9 0.9 4.7": ["instruc"], "9.2 1.9 14.4": ["logrado"], "10.9 8.1 6.3": ["coaxially"], "0.5 14.9 5.0": ["celui"], "17.0 18.8 21.5": ["jerkers"], "-3.3 1.9 3.1": ["hockeyville"], "-1.9 1.6 8.4": ["adnexal"], "13.9 7.7 40.5": ["tonnato"], "-4.6 10.3 6.1": ["carcinoids"], "11.2 4.3 10.8": ["enolase"], "7.7 13.4 18.1": ["aliquam"], "18.1 11.0 23.9": ["hinoki"], "11.7 14.4 13.0": ["hoing"], "5.6 7.2 12.5": ["interdit"], "10.9 0.0 8.9": ["recredentialed"], "9.9 11.0 11.1": ["darin"], "4.5 0.5 9.7": ["hughhefner"], "5.1 1.0 17.7": ["siliciclastic"], "-4.5 5.3 0.8": ["milah"], "16.0 12.3 16.2": ["zoku"], "13.7 12.6 15.3": ["electrocorticography"], "4.3 17.9 19.0": ["centrefire"], "-2.9 6.6 12.8": ["cotransporter"], "8.7 0.2 5.8": ["operaciones"], "8.5 10.1 2.7": ["emotionalization"], "4.3 11.6 13.1": ["megaquakes"], "12.6 -0.0 12.3": ["mucopolysaccharides"], "5.8 10.5 12.8": ["adentro"], "12.6 3.2 8.0": ["bunger"], "0.1 -6.2 10.7": ["stdy"], "-3.9 23.4 8.9": ["bashir"], "7.5 5.4 29.9": ["cruda"], "11.4 8.1 15.1": ["multitable"], "6.4 1.3 3.9": ["bcp"], "5.8 1.7 -4.6": ["uilding"], "-3.3 7.6 11.4": ["tsan"], "11.5 22.4 9.5": ["undanceable"], "13.1 3.6 13.5": ["resurfacers"], "5.2 0.1 3.1": ["mecarbil"], "8.9 -5.0 12.0": ["schede"], "7.1 4.1 6.1": ["asos"], "9.6 -2.4 7.0": ["vehi"], "3.7 -8.2 10.6": ["fara"], "2.9 0.8 17.3": ["lauderdale"], "2.5 12.5 5.3": ["hez"], "10.9 3.2 17.8": ["batti"], "16.0 0.6 2.6": ["ipower"], "6.9 10.5 17.3": ["israelensis"], "-7.4 9.5 4.7": ["kalpana"], "4.6 15.9 8.7": ["metalloproteases"], "3.8 -2.0 5.2": ["powerseller"], "4.9 10.5 3.6": ["gyong"], "1.1 13.6 7.9": ["cristiano"], "14.1 16.4 25.4": ["nogs"], "14.9 15.7 5.0": ["brary"], "-2.6 -1.5 1.8": ["hyong"], "-1.7 4.0 -2.0": ["becocalcidiol"], "18.8 15.7 42.0": ["shortfin"], "-0.8 3.3 1.1": ["subspecialized"], "10.7 9.8 3.7": ["listo"], "0.5 0.2 0.2": ["transseptal"], "5.3 -0.1 5.0": ["offert"], "8.2 22.8 19.1": ["muro"], "8.1 5.5 3.2": ["newsbox"], "-4.0 -5.5 2.5": ["hild"], "6.5 12.1 6.9": ["termes"], "13.3 4.4 3.0": ["ffhoo"], "15.7 15.2 16.9": ["frabjous"], "17.3 0.0 12.4": ["revenueand"], "3.1 7.1 19.5": ["pakiramdam"], "3.3 11.3 2.5": ["zanu"], "1.2 8.7 3.4": ["oversnow"], "-8.6 1.5 1.5": ["recep"], "-0.4 6.1 10.8": ["inamin"], "7.8 9.5 11.3": ["profonde"], "7.4 -3.4 11.2": ["valore"], "4.6 11.4 18.8": ["crue"], "6.0 16.9 6.3": ["tenir"], "3.6 6.4 11.4": ["sapne"], "2.8 11.4 15.9": ["permettre"], "23.3 5.1 21.9": ["clawfoot"], "12.2 19.9 8.9": ["intercepter"], "13.5 -5.2 1.3": ["communiquer"], "-0.4 2.4 0.2": ["farmdoc"], "4.2 1.3 10.7": ["cyhoedd"], "3.2 -2.5 -0.2": ["mobilecast"], "-4.5 5.3 5.9": ["suivants"], "7.7 12.7 7.2": ["utside"], "10.1 13.0 -0.8": ["kml"], "5.9 5.8 11.0": ["andreas"], "0.8 3.5 15.1": ["nagsimula"], "-0.7 12.7 13.8": ["naghahanap"], "5.5 9.4 14.6": ["maher"], "-11.0 18.6 3.1": ["constitu"], "-1.5 -0.8 0.9": ["fons"], "7.4 -10.9 -0.4": ["disinfector"], "7.0 -3.8 10.7": ["fluidised"], "14.2 2.6 18.2": ["zenyatta"], "9.7 -2.7 13.7": ["bailes"], "14.9 8.7 4.8": ["wvsu"], "16.1 6.2 35.1": ["bourguignonne"], "4.7 17.3 11.2": ["magnon"], "-3.3 13.8 8.8": ["dutt"], "8.9 11.2 9.3": ["zanjeer"], "0.1 8.6 4.9": ["chalegi"], "7.1 -8.0 8.4": ["drawmaster"], "1.4 -2.5 -3.2": ["xb"], "-6.3 2.1 13.7": ["daang"], "1.3 10.0 8.8": ["bayit"], "8.9 6.9 18.8": ["nigricans"], "15.3 9.9 13.5": ["prelit"], "5.3 7.4 16.5": ["gagwe"], "-2.4 -4.0 0.4": ["mmunity"], "12.3 15.4 7.8": ["phreaks"], "-4.5 8.2 8.5": ["nonhereditary"], "22.0 13.7 25.1": ["ceiba"], "1.4 10.5 15.3": ["bloodspots"], "-4.1 -1.4 4.4": ["nitrofurantoins"], "15.2 -2.6 -3.6": ["pojistovna"], "1.4 0.4 16.1": ["papaano"], "-8.1 -3.3 7.8": ["barabar"], "7.5 4.3 3.5": ["tition"], "6.2 6.2 8.7": ["welke"], "0.5 5.8 5.5": ["dermatologically"], "7.4 3.6 -0.3": ["eaton"], "-0.4 5.2 7.1": ["ebx"], "8.4 15.8 5.9": ["lool"], "0.1 10.4 16.0": ["disas"], "6.2 6.5 21.0": ["gles"], "8.8 7.2 3.9": ["fatbellybella"], "7.5 14.2 8.8": ["subaverage"], "19.6 12.7 23.0": ["huxleyi"], "-3.2 9.4 16.5": ["imbestigahan"], "13.2 7.9 9.2": ["solutely"], "15.9 10.7 8.9": ["hydropneumatic"], "9.4 14.1 4.8": ["damag"], "5.5 9.5 -2.4": ["ndc"], "2.9 7.0 16.3": ["drogas"], "15.2 6.3 22.7": ["siam"], "-1.1 -1.8 8.9": ["febrero"], "2.7 16.3 7.3": ["organizatio"], "1.6 2.4 19.3": ["pygmaeus"], "-7.3 -1.1 7.6": ["ndividual"], "13.1 13.3 25.3": ["wagger"], "-2.5 -1.7 0.8": ["contrairement"], "11.3 1.7 5.7": ["ordinateurs"], "3.2 9.2 10.9": ["wholelife"], "8.2 2.1 0.9": ["trk"], "4.6 -2.1 8.3": ["superiore"], "7.4 6.5 11.7": ["fynd"], "4.5 5.9 3.9": ["zil"], "1.2 15.6 12.1": ["pegnivacogin"], "1.0 0.2 4.3": ["cardiorenal"], "6.3 5.4 6.9": ["componentes"], "8.6 4.9 16.2": ["parche"], "11.3 6.7 26.5": ["silvertip"], "4.6 7.3 4.9": ["signa"], "-2.3 -8.5 2.0": ["obser"], "-0.7 1.8 16.7": ["sansad"], "-2.2 4.4 2.2": ["physi"], "9.5 13.5 9.1": ["travolta"], "3.9 -10.4 11.9": ["tival"], "7.9 20.8 9.7": ["suspensful"], "10.3 -3.2 7.8": ["tich"], "2.8 -2.4 -2.6": ["hydrofluoric"], "-2.3 11.2 14.2": ["palaging"], "9.5 7.9 21.1": ["chowpatty"], "-3.9 -4.1 6.3": ["monds"], "3.7 16.1 4.7": ["microphysical"], "15.6 12.4 18.2": ["tasman"], "9.5 9.3 16.0": ["conocimiento"], "6.4 9.2 10.6": ["mailblog"], "5.2 0.6 -10.3": ["ofoperations"], "0.2 -2.3 12.6": ["posiciones"], "4.2 4.0 1.3": ["availab"], "8.2 6.3 3.6": ["orthosteric"], "13.0 18.7 10.7": ["nasolabial"], "11.2 -1.3 6.8": ["slipdress"], "7.9 1.1 12.9": ["elton"], "-1.3 13.9 13.9": ["nanggaling"], "12.2 -3.2 2.9": ["bioceutical"], "9.6 -2.5 9.5": ["openi"], "-7.9 -10.4 6.1": ["iors"], "6.2 7.1 12.0": ["christa"], "-0.7 8.3 8.8": ["pramukhs"], "13.2 12.3 20.0": ["masseter"], "2.6 10.3 22.5": ["makasama"], "7.9 4.0 4.5": ["tunc"], "8.9 0.7 -0.0": ["torsemide"], "12.3 -0.1 13.4": ["fesh"], "-6.1 -1.4 6.5": ["tarjeta"], "2.5 4.3 -0.6": ["huffingtonpost"], "7.1 -5.0 -0.5": ["biojet"], "10.2 2.8 14.9": ["medicina"], "8.0 2.5 7.9": ["choupal"], "-2.4 1.3 16.5": ["umabot"], "20.6 4.5 18.1": ["psychodelic"], "-5.8 6.0 6.2": ["myoclonic"], "10.3 -3.3 11.0": ["andadministrative"], "4.1 4.1 18.6": ["shortable"], "-2.4 10.5 6.8": ["nakakita"], "3.5 3.5 11.9": ["garantie"], "9.9 5.8 11.6": ["blaid"], "5.8 17.7 22.2": ["jessamine"], "2.7 5.0 14.7": ["distancia"], "0.3 4.9 7.8": ["anada"], "12.6 28.3 14.2": ["ostrichlike"], "6.6 11.3 9.3": ["dihydrogen"], "13.9 25.5 17.9": ["unvirtuous"], "5.4 0.3 9.5": ["decubitus"], "5.2 10.9 10.6": ["diovan"], "-4.6 8.4 10.3": ["atonic"], "20.4 -6.3 8.0": ["swimsuited"], "5.2 10.4 15.8": ["zallouh"], "6.7 -0.8 6.2": ["zih"], "18.4 5.3 27.1": ["seabound"], "2.2 10.7 5.9": ["daag"], "-1.1 11.7 -0.3": ["indemnifiable"], "-5.6 -8.6 7.5": ["dftd"], "0.8 2.9 7.6": ["desonide"], "7.2 11.2 14.7": ["chinta"], "15.2 -0.2 29.4": ["pitahaya"], "-3.9 10.6 7.4": ["netmail"], "16.9 12.9 15.4": ["paraphanelia"], "4.9 -0.2 13.3": ["golygu"], "4.5 8.2 9.8": ["plazo"], "-1.6 9.3 14.5": ["sumunod"], "7.6 5.9 7.0": ["hda"], "-4.9 12.0 6.1": ["scri"], "5.7 5.5 6.5": ["ocial"], "7.9 5.3 11.9": ["photograpy"], "6.7 -3.1 7.5": ["lthr"], "0.9 6.8 14.1": ["uusap"], "9.5 3.5 2.2": ["fourcylinder"], "0.9 4.6 4.4": ["hagen"], "6.2 3.4 -2.7": ["habilitated"], "-8.8 28.1 14.3": ["overtasked"], "-3.6 7.4 4.7": ["abadis"], "6.7 15.8 1.5": ["preprogramed"], "10.0 4.8 13.1": ["stratocumulus"], "-2.2 4.1 32.4": ["lowbush"], "8.2 15.6 12.4": ["downspeed"], "13.1 1.1 -1.2": ["edel"], "15.1 17.9 30.9": ["whitecapped"], "3.9 15.3 21.4": ["pollinations"], "-0.2 5.6 4.1": ["solu"], "10.4 11.8 8.7": ["cotter"], "6.6 0.9 31.9": ["lomi"], "3.2 -3.1 6.5": ["confe"], "4.6 0.9 0.7": ["valores"], "14.9 8.6 8.9": ["ilife"], "-2.3 3.4 10.0": ["entendu"], "1.7 4.9 17.2": ["lanta"], "3.7 -1.7 6.5": ["resorbing"], "11.4 -4.8 23.0": ["robiola"], "8.5 3.0 13.2": ["electroformed"], "4.6 -6.8 -3.6": ["screenprinter"], "3.5 -8.6 3.6": ["bahl"], "9.3 9.6 16.0": ["boylike"], "-1.0 -1.2 1.4": ["hcr"], "1.2 7.6 1.2": ["antimitotic"], "14.5 1.8 1.1": ["flextop"], "1.3 9.2 12.2": ["odontoid"], "3.7 0.6 14.8": ["degloving"], "0.0 13.7 21.7": ["meltoff"], "-2.7 8.9 13.3": ["nabanggit"], "6.1 8.4 10.4": ["alcanzar"], "3.3 6.8 12.9": ["madhya"], "16.9 4.2 30.1": ["drummies"], "-4.7 1.6 -0.6": ["responsi"], "7.6 -1.1 4.2": ["llegado"], "9.8 8.2 13.7": ["unioned"], "12.7 11.0 6.6": ["nonionizing"], "0.4 6.2 17.1": ["aktor"], "14.4 5.3 5.9": ["gluers"], "4.6 12.0 23.7": ["yahd"], "0.8 7.7 11.2": ["mcconnell"], "5.8 4.5 7.1": ["atics"], "-3.9 -2.6 15.3": ["sunod"], "11.2 3.4 28.2": ["siew"], "17.4 11.6 45.2": ["shrimplike"], "0.3 5.0 8.4": ["saphenous"], "3.1 5.8 -0.7": ["xperia"], "10.1 -5.3 4.8": ["polypropylenes"], "14.8 9.9 26.7": ["undecorating"], "18.3 6.8 19.2": ["hunka"], "0.4 8.6 5.8": ["schafft"], "2.2 -0.6 9.5": ["fakta"], "0.5 4.4 7.4": ["logues"], "0.4 1.8 20.7": ["fatales"], "4.4 -2.0 8.2": ["monium"], "-1.0 9.8 -0.1": ["terna"], "3.9 0.5 20.8": ["pondless"], "5.9 17.3 6.8": ["dhtml"], "2.3 -3.7 7.4": ["nakasama"], "10.4 13.6 11.5": ["nemawashi"], "6.1 3.2 5.1": ["leyes"], "0.4 5.4 8.7": ["hyoung"], "8.0 9.7 14.9": ["wakings"], "1.7 -4.2 0.5": ["glyconutritional"], "4.0 -0.5 0.1": ["defeasing"], "4.9 13.4 10.4": ["compromiso"], "0.8 2.8 7.6": ["permitir"], "18.8 -3.7 -2.9": ["xplore"], "13.4 6.9 12.8": ["comercio"], "17.8 1.3 6.1": ["entertaintment"], "7.0 15.5 10.9": ["elizadushku"], "3.9 7.4 10.8": ["leeze"], "3.9 5.7 7.6": ["pleine"], "12.9 -3.2 4.3": ["derde"], "7.5 11.4 18.1": ["pehli"], "-2.6 17.4 1.4": ["sufferage"], "6.9 8.4 9.7": ["tsked"], "17.1 2.1 14.6": ["fireknife"], "12.7 10.9 16.5": ["derp"], "11.1 7.6 14.4": ["toco"], "1.9 15.5 14.2": ["macrofinancial"], "-7.7 6.1 2.1": ["olitical"], "-3.8 2.6 15.6": ["kabilang"], "2.6 2.0 11.3": ["btl"], "7.3 17.3 16.9": ["poda"], "-11.7 -1.2 7.0": ["preventionist"], "-2.4 4.2 5.9": ["atomicity"], "12.0 12.8 22.3": ["jolokia"], "18.9 2.2 44.1": ["lumpfish"], "8.7 6.1 7.0": ["potentialed"], "4.0 10.4 5.6": ["subir"], "5.3 10.2 10.9": ["jamin"], "8.7 -1.2 1.8": ["soluciones"], "11.0 3.4 6.6": ["miembro"], "7.5 8.8 19.6": ["reimplanting"], "6.6 7.2 15.7": ["hinihingi"], "13.8 6.8 3.6": ["multitrillion"], "5.2 13.6 7.5": ["persulfate"], "1.3 10.8 7.0": ["corticospinal"], "4.7 2.3 11.5": ["riesgo"], "6.9 1.0 9.5": ["beneficio"], "9.1 2.8 14.2": ["terres"], "17.9 7.7 30.9": ["moonpie"], "1.9 2.5 4.9": ["transforaminal"], "12.6 9.4 10.7": ["veterbrae"], "4.6 15.3 1.4": ["vigiling"], "5.7 1.8 16.9": ["kulit"], "-0.6 2.6 0.4": ["rities"], "-2.9 -3.2 -2.4": ["urgence"], "-7.2 2.4 -2.8": ["ustice"], "-6.8 -2.3 6.2": ["duces"], "2.2 -8.1 -3.7": ["cedex"], "5.9 5.8 11.1": ["recv"], "-3.1 7.7 14.0": ["southeasternmost"], "0.1 8.7 4.9": ["viennent"], "1.9 -2.3 16.6": ["soeur"], "-5.3 8.9 9.5": ["fficers"], "7.9 10.0 7.4": ["skimmable"], "9.2 4.5 5.6": ["amoxil"], "20.9 7.3 15.7": ["forebody"], "-0.3 16.2 2.6": ["indisputed"], "10.8 15.4 17.5": ["aquifolium"], "12.3 15.6 17.7": ["vibrissae"], "9.9 1.7 7.5": ["livello"], "14.7 13.6 10.7": ["cyberscams"], "9.5 10.6 12.3": ["poundingly"], "7.1 0.4 2.3": ["pharmacie"], "7.9 -2.3 6.1": ["founda"], "2.9 4.3 5.4": ["cyanate"], "3.5 21.6 12.1": ["qn"], "-2.5 12.5 16.4": ["panas"], "8.7 12.4 11.8": ["tisk"], "5.8 4.8 13.0": ["dupa"], "3.5 -1.2 2.3": ["oods"], "12.4 1.1 3.8": ["katyperry"], "3.3 2.0 -0.3": ["rupt"], "14.2 4.3 21.6": ["emtpy"], "7.8 7.1 5.0": ["perience"], "0.7 10.5 4.4": ["intramyocardial"], "8.0 20.0 4.5": ["impersonalized"], "7.3 6.7 12.8": ["hendra"], "3.1 3.1 12.6": ["mastalgia"], "6.9 -2.0 17.6": ["itc"], "-0.6 8.5 0.2": ["akhand"], "13.4 9.7 17.0": ["jubbly"], "12.5 9.2 12.9": ["sweepin"], "6.2 -5.1 4.6": ["travailleurs"], "1.4 14.0 3.5": ["crossband"], "12.6 15.9 4.9": ["feelplus"], "9.6 -5.3 1.2": ["nonpension"], "-0.2 10.4 14.1": ["criminaliens"], "6.8 4.3 16.6": ["vember"], "12.6 -0.1 14.6": ["dfw"], "2.0 10.0 -0.6": ["myeloproliferative"], "1.8 -0.7 16.6": ["lwt"], "3.6 31.9 8.6": ["exoatmospheric"], "14.0 5.0 9.8": ["reorts"], "-9.2 7.7 -3.3": ["redeclared"], "6.3 24.3 12.5": ["noforn"], "2.3 8.9 12.8": ["honi"], "8.6 0.2 0.1": ["deseal"], "14.7 11.5 21.3": ["megafaunal"], "6.0 1.0 0.4": ["dichloroethane"], "18.8 15.8 17.0": ["facedly"], "1.5 7.6 11.7": ["bawas"], "-0.8 7.7 1.8": ["atkinson"], "-2.4 10.9 0.3": ["reperforming"], "9.7 29.8 -1.7": ["defeatest"], "8.2 7.1 3.6": ["haemo"], "9.4 11.2 0.7": ["harald"], "13.8 14.1 4.7": ["superfamous"], "7.7 -7.1 11.6": ["fayette"], "14.2 4.3 2.7": ["noyau"], "7.3 11.1 20.2": ["kikuya"], "3.7 4.6 15.9": ["osteologist"], "9.3 9.9 4.6": ["bitlocker"], "4.2 1.4 18.3": ["concho"], "7.0 5.7 13.1": ["olas"], "19.1 1.6 3.7": ["timeforcake"], "-1.0 -1.1 12.0": ["mababa"], "20.6 18.4 11.5": ["astromech"], "5.6 6.1 15.2": ["territoire"], "15.0 9.6 18.2": ["feuilles"], "-5.8 8.1 4.7": ["ungranted"], "8.4 22.2 12.0": ["campaigne"], "10.8 9.0 17.5": ["europaea"], "8.4 -4.0 16.1": ["penderfyniad"], "1.1 4.2 8.5": ["letes"], "18.3 4.6 9.5": ["nonweapons"], "-4.2 5.6 11.3": ["nale"], "7.0 10.5 15.0": ["horsecollar"], "5.0 9.6 10.7": ["objetivos"], "3.9 4.8 10.0": ["mathews"], "17.1 6.9 14.0": ["normous"], "24.1 21.2 15.4": ["whumping"], "1.0 -2.9 6.2": ["voulez"], "2.0 8.3 18.6": ["kalagayan"], "7.5 21.5 7.6": ["remilitarizing"], "18.7 -7.4 14.0": ["dollmakers"], "-5.0 5.2 4.5": ["xlib"], "-3.3 -0.2 13.2": ["approa"], "3.4 10.7 23.3": ["fatt"], "-2.2 9.6 9.8": ["hypervariable"], "-0.9 -5.1 10.9": ["polypills"], "-6.5 -2.9 8.2": ["sural"], "5.6 13.5 16.4": ["kawawa"], "1.7 26.3 -4.1": ["ratline"], "15.5 6.7 21.0": ["lunchables"], "-3.1 2.5 4.2": ["maange"], "2.7 -1.7 7.5": ["poojan"], "-4.8 4.3 2.3": ["opportuni"], "-3.1 3.4 5.6": ["verletzt"], "1.6 7.2 19.7": ["pagmamahal"], "-0.5 -1.0 11.3": ["nondisparagement"], "-3.9 12.8 16.7": ["estime"], "0.1 13.9 13.8": ["endurorob"], "10.4 -0.5 11.7": ["vivants"], "9.5 7.1 1.4": ["opoc"], "4.5 2.7 14.1": ["mejorar"], "16.5 8.3 8.5": ["vibrationally"], "3.9 10.7 11.4": ["komma"], "-2.2 10.0 4.7": ["ensu"], "-2.5 8.3 6.5": ["thoracoabdominal"], "1.4 -4.0 3.5": ["nization"], "5.6 3.8 10.4": ["mediakit"], "10.2 4.0 3.7": ["glycosylase"], "7.0 4.6 19.4": ["oleracea"], "-7.0 -8.2 1.6": ["interrater"], "18.5 11.3 27.3": ["tickety"], "-4.7 8.9 19.4": ["papayag"], "3.1 2.8 3.8": ["nephronophthisis"], "15.6 11.3 21.5": ["ooey"], "8.6 16.8 3.6": ["unconciousness"], "-2.0 1.8 -1.1": ["carbinol"], "5.9 0.3 8.4": ["responsabile"], "15.5 0.1 34.0": ["gobhi"], "10.7 8.9 14.9": ["pewee"], "2.2 7.5 14.0": ["phalangeal"], "7.8 -0.5 -1.0": ["endomechanical"], "9.8 29.6 13.6": ["antiship"], "2.8 3.1 12.4": ["likod"], "19.8 9.2 23.3": ["froot"], "-0.9 14.4 9.8": ["tova"], "9.1 0.9 14.6": ["undriven"], "13.1 -1.3 7.9": ["ontwikkeling"], "5.7 11.1 20.0": ["entrar"], "6.3 10.6 -1.4": ["transpor"], "4.3 -0.6 5.9": ["panies"], "8.2 8.7 7.7": ["phonenumber"], "7.1 -4.9 -2.2": ["carbetocin"], "6.9 4.2 13.2": ["tendencia"], "-3.7 2.1 10.6": ["bronchoalveolar"], "6.2 -2.7 10.3": ["finanziari"], "14.8 -0.5 16.9": ["ovenable"], "13.3 16.8 7.8": ["grib"], "5.2 2.4 11.2": ["nombreuses"], "18.8 -3.2 16.1": ["jonesi"], "5.9 3.2 15.5": ["cincher"], "6.3 2.9 3.6": ["permettent"], "10.3 -9.3 -5.1": ["osiguranje"], "3.7 5.8 5.5": ["romazarit"], "10.4 -0.5 28.3": ["petri"], "8.3 3.5 11.8": ["epiblast"], "5.1 9.8 14.5": ["kereta"], "2.9 -3.2 10.5": ["yehz"], "-7.6 -3.9 6.2": ["chakku"], "8.7 8.3 11.8": ["lpfisher"], "6.0 12.3 17.3": ["vivian"], "11.6 6.6 14.8": ["unretrieved"], "6.9 2.9 10.0": ["lincomycin"], "-0.2 12.3 15.3": ["endophytic"], "-1.1 14.1 9.6": ["omeone"], "7.9 3.0 13.5": ["travelgirl"], "18.9 2.5 21.4": ["bellbottom"], "10.2 -3.7 8.2": ["carbonisation"], "10.9 7.0 29.2": ["microgreen"], "16.5 19.1 20.1": ["fouette"], "-9.3 30.3 7.3": ["rodef"], "2.9 10.5 4.1": ["racialise"], "8.4 -1.2 11.6": ["teithio"], "-3.0 10.8 4.9": ["epublican"], "7.6 -2.3 7.4": ["antihormonal"], "13.3 13.7 25.6": ["endagered"], "-2.5 9.8 13.9": ["hasya"], "-0.8 2.9 5.8": ["karamcharis"], "11.1 0.3 17.3": ["avantages"], "14.9 11.9 15.0": ["lahm"], "10.4 5.6 37.6": ["groundlines"], "14.3 7.5 21.4": ["unthawing"], "8.4 7.4 5.2": ["blogo"], "6.4 0.2 10.9": ["vasquez"], "4.8 1.1 14.7": ["palpations"], "15.5 31.5 0.3": ["weaponed"], "10.3 19.6 15.9": ["axehandle"], "-2.1 10.9 3.0": ["stration"], "0.4 5.5 8.8": ["uveal"], "16.2 6.7 8.7": ["appareil"], "-0.7 3.8 8.9": ["countervailable"], "-8.6 -1.4 -10.5": ["electrograms"], "4.9 15.2 11.0": ["neuraminidases"], "-0.2 10.1 5.4": ["dysthymic"], "-6.3 2.8 4.4": ["custodes"], "5.1 13.9 8.8": ["decompressive"], "1.9 3.9 10.2": ["dlink"], "9.3 12.7 10.1": ["iful"], "7.5 15.3 2.3": ["undyingly"], "17.8 -0.7 13.2": ["tafetta"], "14.7 13.9 3.8": ["weap"], "-1.8 -1.5 4.5": ["glucosylceramide"], "7.8 7.9 9.8": ["shapen"], "3.5 3.2 0.2": ["sorbed"], "0.9 7.0 14.0": ["radiocontrast"], "2.6 0.1 4.5": ["marm"], "14.3 2.5 15.4": ["jardinieres"], "0.8 0.9 6.6": ["doke"], "8.1 8.4 11.4": ["evitar"], "-0.7 7.8 13.1": ["gumagawa"], "10.9 2.0 27.8": ["croute"], "2.0 0.8 11.6": ["byddai"], "4.2 3.3 -6.0": ["teleprotection"], "8.2 6.1 9.8": ["illegalizing"], "11.3 10.5 22.6": ["peameal"], "8.2 12.9 12.9": ["nonmedicinal"], "5.8 0.9 7.7": ["nesday", "cliniques"], "8.5 -1.4 -4.4": ["esign"], "11.3 7.3 -0.9": ["thecentre"], "4.9 4.0 1.0": ["diplomatique"], "12.4 -1.9 9.5": ["midpark"], "3.1 10.7 -7.6": ["paralled"], "8.9 14.3 31.9": ["longspurs"], "11.4 14.0 6.8": ["gaying"], "9.9 4.1 29.4": ["sambol"], "8.5 10.7 13.6": ["mortice"], "8.9 4.3 0.7": ["xpm"], "14.2 3.1 -2.3": ["fabricant"], "19.8 5.1 20.4": ["rinky"], "8.5 6.2 32.9": ["flavescens"], "6.6 15.6 25.1": ["frogeye"], "-4.5 -4.9 -6.3": ["innova"], "2.0 9.6 11.2": ["tristique"], "-0.2 -1.3 5.6": ["exhibi"], "8.1 2.5 5.7": ["geleden"], "5.8 15.6 6.7": ["jamas"], "6.4 -8.9 -7.9": ["ecg"], "9.2 1.7 11.1": ["angioma"], "0.7 -8.6 -7.1": ["rohs"], "8.7 15.1 8.2": ["herin"], "6.2 2.5 8.0": ["reopeners"], "4.6 -1.4 6.4": ["marketwatch"], "4.8 12.1 17.9": ["hidey"], "5.7 9.1 10.3": ["encephalopathies"], "-3.2 -4.3 -0.4": ["dnevnik"], "10.8 10.2 15.2": ["midtour"], "-5.9 15.9 13.5": ["atti"], "6.7 12.3 16.4": ["deacetylases"], "5.0 4.3 3.9": ["resecuritized"], "11.2 1.0 3.1": ["ascorbic"], "-3.8 16.6 1.9": ["shewn"], "-6.9 -3.1 4.2": ["nonpub"], "6.7 24.1 8.8": ["deprecatingly"], "3.4 9.4 18.7": ["librium"], "13.9 6.9 13.8": ["wetters"], "4.6 6.7 17.8": ["entrenamiento"], "7.2 10.8 13.8": ["flagellations"], "19.6 12.9 23.1": ["lucidum"], "8.0 2.5 10.5": ["ddyn"], "10.8 8.0 14.9": ["crunchingly"], "5.3 -11.0 -1.4": ["dehl"], "-7.8 5.1 9.3": ["thrombocytopenic"], "4.3 6.5 2.3": ["promt"], "22.8 13.4 6.4": ["dyson"], "4.0 7.4 7.9": ["natyam"], "1.4 5.0 12.1": ["piezas"], "13.8 -6.0 2.0": ["utenti"], "10.0 3.6 7.2": ["sparta"], "0.3 4.1 3.2": ["excep"], "10.0 2.1 5.6": ["amphoteric"], "3.5 3.3 13.4": ["palitan"], "-0.5 -2.6 12.1": ["postrelease"], "-5.5 -5.5 5.7": ["decilitre"], "1.5 -0.5 7.2": ["iyer"], "3.4 16.2 1.6": ["sphenoid"], "4.5 17.8 14.9": ["xanthus"], "7.8 10.9 28.1": ["crackery"], "13.3 14.3 10.3": ["weisse"], "10.5 11.6 5.3": ["fuerzas"], "0.7 6.2 15.1": ["totequadpot"], "13.0 15.2 6.9": ["deprogrammer"], "2.3 13.6 -7.0": ["bereit"], "-0.5 0.4 3.9": ["shcools"], "4.7 3.9 8.4": ["forkhead"], "3.0 2.1 14.5": ["gogledd"], "14.5 3.2 24.9": ["quartersawn"], "-2.1 15.4 3.8": ["yalla"], "19.7 15.4 25.4": ["firestick"], "2.2 5.7 10.4": ["llamar"], "4.8 11.2 3.9": ["presummit"], "5.3 11.9 4.8": ["societywide"], "10.7 7.1 16.1": ["imbrication"], "-5.6 -4.4 4.0": ["ferred"], "5.8 14.4 8.2": ["argc"], "2.3 5.1 9.1": ["perpetua"], "12.6 7.6 10.1": ["cooee"], "2.0 6.2 14.3": ["estructura"], "15.4 26.4 17.4": ["bottome"], "11.6 4.4 34.0": ["harina"], "12.2 13.2 8.2": ["whoopla"], "2.0 -10.8 14.3": ["ditions"], "4.2 3.7 18.9": ["unstabilised"], "2.7 6.7 18.6": ["deporte"], "-3.9 14.1 5.0": ["klal"], "-3.6 5.3 1.4": ["therof"], "8.6 -12.0 -2.5": ["tijdens"], "-1.5 6.6 -2.6": ["museveni"], "-0.1 10.6 8.8": ["viously"], "5.6 10.1 18.2": ["beltran"], "6.7 8.5 8.8": ["informacion"], "-2.3 -1.1 7.5": ["ncil"], "9.7 20.4 8.5": ["unmixing"], "5.2 8.9 8.3": ["fstab"], "11.3 6.2 9.0": ["meest"], "7.5 -7.4 34.0": ["bucco"], "2.6 6.4 2.7": ["tosuccessfully"], "-0.1 3.2 8.9": ["dorsomedial"], "3.2 -0.6 13.3": ["bikram"], "-4.2 20.2 4.1": ["lems"], "10.9 5.5 20.4": ["dejeuner"], "7.1 14.9 4.6": ["uestion"], "-4.3 12.2 6.4": ["vande"], "5.8 8.6 0.2": ["countlessly"], "-2.2 8.3 15.3": ["epekto"], "10.6 15.9 8.5": ["spk"], "5.0 13.3 5.8": ["rakha"], "10.9 12.6 21.0": ["mander"], "8.5 7.4 6.4": ["inven"], "-2.3 10.9 2.4": ["togain"], "1.3 13.0 15.7": ["occa"], "-5.5 7.2 2.5": ["bondswoman"], "-0.4 4.5 3.5": ["zquez"], "1.7 -2.3 5.5": ["septuple"], "9.6 0.3 -0.4": ["alkylates"], "17.7 13.7 2.8": ["uneviable"], "13.9 3.5 18.9": ["llawer"], "0.1 -7.3 -2.3": ["thinksound"], "4.0 5.4 16.8": ["textes"], "9.3 8.1 16.0": ["comedogenic"], "-5.1 10.0 10.3": ["vena"], "3.2 4.9 1.4": ["troversy"], "3.9 -1.3 1.5": ["shoh"], "-4.8 -1.8 5.5": ["pakki"], "4.2 4.3 11.8": ["perinuclear"], "8.0 1.3 43.7": ["rangoon"], "-0.5 6.4 1.4": ["evertontv"], "-4.7 3.1 2.9": ["abor"], "-2.8 -1.0 5.7": ["nonsevere"], "12.3 4.5 32.9": ["lotte"], "8.7 0.8 -2.6": ["oilbody"], "-1.1 0.3 -0.3": ["siehe"], "8.5 0.0 4.2": ["edg"], "4.1 8.6 6.2": ["diversional"], "8.3 16.0 1.7": ["cuota"], "6.3 9.6 11.0": ["adipiscing"], "-3.0 0.5 -1.0": ["phosphorylase"], "12.9 6.2 25.8": ["capades"], "13.7 -9.7 -4.4": ["inzake"], "20.1 1.0 14.9": ["geoelectric"], "8.0 0.2 1.6": ["resistencia"], "0.5 12.4 5.1": ["revivifies"], "11.6 11.3 16.3": ["barani"], "9.4 13.1 15.7": ["noches"], "-15.2 -3.4 10.9": ["tices"], "11.3 16.9 8.3": ["jayson"], "9.7 5.4 5.0": ["crossownership"], "0.2 6.1 9.9": ["doned"], "4.2 12.1 -0.3": ["avez"], "3.5 10.0 4.4": ["ladygaga"], "10.1 11.5 18.1": ["caminata"], "12.2 21.9 14.8": ["scarborough"], "0.3 2.3 9.1": ["tero"], "9.7 13.4 17.8": ["uric"], "9.9 2.1 16.4": ["stearic"], "4.3 -4.5 10.6": ["healthplans"], "-11.5 1.2 5.3": ["wz"], "0.6 19.7 15.2": ["radiational"], "12.6 -1.8 6.0": ["direttamente"], "2.5 2.4 8.7": ["opers"], "16.1 23.6 15.4": ["gevalt"], "9.7 -1.1 10.8": ["actovegin"], "2.5 0.4 -3.6": ["stitution"], "0.0 7.5 8.5": ["wordily"], "5.5 0.6 11.7": ["espagnol"], "20.0 4.3 32.9": ["monkeypod"], "1.0 12.6 5.8": ["identif"], "19.9 9.1 8.4": ["groundscare"], "7.6 3.6 3.5": ["sicurezza"], "2.7 1.3 8.6": ["correo"], "12.4 17.0 10.9": ["sacrific"], "11.3 -2.6 13.0": ["dichloro"], "7.3 14.5 5.2": ["iseedocs"], "3.6 9.7 -5.8": ["vania"], "1.5 -5.9 3.0": ["arquitectura"], "3.5 12.3 27.5": ["arrowleaf"], "3.5 11.3 7.5": ["pyogenes"], "4.9 0.7 3.2": ["disque"], "-3.5 7.6 8.8": ["alkalosis"], "5.3 3.6 6.5": ["preshift"], "8.8 7.7 8.5": ["becaks"], "5.3 13.7 16.9": ["bdelloid"], "7.7 9.1 6.3": ["untrack"], "8.8 8.8 6.2": ["carga"], "8.7 9.2 23.9": ["tenderizers"], "0.9 10.9 12.7": ["napag"], "-7.5 10.2 4.2": ["zongo"], "21.8 4.7 20.6": ["tearer"], "0.4 -9.3 11.8": ["zell"], "1.2 2.6 7.2": ["diciembre"], "-3.1 1.5 5.0": ["propionic"], "7.3 -3.7 24.4": ["pekoe"], "8.0 3.5 5.8": ["circuito"], "10.0 9.6 9.9": ["arkosic"], "14.4 5.5 35.1": ["parmentier"], "10.8 -3.3 9.8": ["estima"], "0.7 11.8 9.4": ["midrate"], "5.5 19.9 15.0": ["klitschko"], "8.4 17.3 30.3": ["akekee"], "-0.6 7.5 14.3": ["glabellar"], "6.9 13.6 1.7": ["statal"], "12.3 33.3 -3.8": ["counterspies"], "-5.0 4.5 4.9": ["sumption"], "14.3 9.4 9.4": ["caatoosee"], "20.7 4.1 17.6": ["herky"], "5.2 -1.3 10.3": ["kayagum"], "-4.8 6.3 7.7": ["sinong"], "-5.8 -8.5 -5.8": ["lihk"], "10.4 -0.3 9.6": ["multinutrient"], "9.9 9.5 11.2": ["fatafati"], "7.4 16.1 11.7": ["septicemic"], "0.9 1.3 5.1": ["meye"], "1.2 9.3 4.6": ["facesaving"], "-0.3 -4.6 6.2": ["uhz"], "9.2 18.1 13.5": ["maddog"], "3.5 37.2 -0.0": ["terrist"], "-6.2 0.1 10.3": ["sihs"], "9.0 -4.1 7.6": ["fibroin"], "5.2 -1.2 -0.2": ["ghter"], "1.9 -1.2 12.0": ["luding"], "7.8 18.4 17.9": ["dipset"], "24.5 13.3 7.1": ["momumental"], "5.0 2.1 14.0": ["cymryd"], "14.8 13.9 23.1": ["hemolysin"], "-11.6 -0.9 4.4": ["dhayya"], "11.4 7.3 14.8": ["birthin"], "0.1 2.6 29.4": ["raab"], "12.1 7.0 33.3": ["duckbilled"], "2.1 9.0 16.4": ["ichiro"], "3.3 16.9 14.5": ["interband"], "9.3 6.0 11.9": ["croony"], "7.4 6.6 13.5": ["regarde"], "-3.0 10.4 15.4": ["katawhan"], "16.3 26.9 11.9": ["bonecrushing"], "7.8 -8.6 7.8": ["encuentra"], "-7.1 9.7 10.6": ["husto"], "12.8 8.4 6.2": ["soporte"], "11.0 2.0 14.9": ["anomodonts"], "2.5 9.9 6.9": ["minitrial"], "6.2 14.1 25.9": ["attenuata"], "3.2 19.7 26.8": ["bloodedness"], "3.9 1.7 11.1": ["ewwel"], "0.9 7.4 4.3": ["transarterial"], "4.3 3.1 -2.0": ["istry"], "17.0 5.7 9.5": ["brakelights"], "13.9 5.7 17.1": ["fooot"], "4.3 8.6 6.4": ["defrocks"], "5.1 3.6 6.3": ["bestimmte"], "8.4 -1.6 -3.5": ["endopeptidase"], "10.9 0.5 7.9": ["alicaforsen"], "6.7 3.3 10.3": ["kese"], "7.5 -1.6 16.8": ["hyok"], "5.7 -3.3 0.3": ["photorefractive"], "2.0 7.3 0.7": ["efector"], "6.1 10.7 22.1": ["bando"], "10.0 12.1 -3.0": ["haemorrage"], "1.8 4.8 13.2": ["ngern"], "10.0 17.0 7.0": ["shampooer"], "2.3 2.0 9.8": ["tember"], "0.2 10.6 15.2": ["panig"], "2.6 9.9 13.2": ["andcost"], "7.5 4.0 6.6": ["persbericht"], "-13.9 -0.9 -0.8": ["fficer"], "14.4 0.4 17.1": ["galvannealed"], "8.7 -4.7 10.2": ["cholesteric"], "-7.8 5.4 0.8": ["bacteremic"], "16.6 14.7 32.9": ["saker"], "4.4 14.4 15.0": ["seaface"], "-2.5 9.1 16.4": ["indel"], "-6.2 -9.2 0.1": ["winbacks"], "1.0 12.4 18.9": ["yakka"], "-0.8 5.6 5.5": ["specifi"], "4.2 3.9 6.6": ["partum"], "13.4 -0.7 2.9": ["toannounce"], "-2.8 26.5 10.9": ["pulitzer"], "5.5 9.1 4.9": ["pronouncers"], "7.6 15.8 23.4": ["nelsons"], "-5.0 0.5 -0.8": ["supersire"], "14.1 -5.7 -2.2": ["kika"], "-3.0 -13.6 8.9": ["sheridan"], "6.8 3.6 9.1": ["ganancias"], "-1.0 3.1 3.9": ["netrin"], "-3.0 8.6 20.5": ["lateralis"], "11.4 9.0 25.2": ["rattus"], "4.7 1.0 -0.7": ["lopment"], "10.8 4.3 26.5": ["anomala"], "3.7 5.2 11.4": ["taxaide"], "5.4 23.9 12.8": ["unconfessed"], "-3.4 9.9 3.7": ["freindship"], "7.9 10.3 14.5": ["hoosh"], "9.0 -1.7 1.2": ["lipidology"], "1.1 14.8 6.9": ["rotos"], "-1.3 5.8 8.6": ["nents"], "17.1 16.7 33.2": ["cabriole"], "2.9 8.8 24.4": ["furbearing"], "1.1 2.6 4.8": ["emptor"], "6.0 9.0 2.0": ["nonprecedential"], "-8.0 9.3 3.9": ["macroglobulinemia"], "9.6 1.9 17.7": ["garni"], "3.1 2.4 11.9": ["erating"], "7.0 4.7 4.8": ["nationales"], "3.0 6.1 18.0": ["quotational"], "3.4 -8.3 -1.7": ["parently"], "-0.3 3.6 3.0": ["kadisha"], "-2.4 2.4 4.3": ["vations"], "-6.0 -3.8 3.9": ["uct"], "6.1 4.2 4.6": ["lisfranc"], "3.5 0.4 8.1": ["autorisation"], "3.8 3.3 1.2": ["sociation"], "4.3 5.4 4.9": ["oxynitride"], "0.1 0.5 11.3": ["detto"], "12.7 9.1 14.2": ["tsunamigenic"], "13.3 0.5 23.8": ["carrybags"], "15.1 -4.8 8.8": ["sharesave"], "7.9 22.0 3.2": ["maneuverer"], "11.6 9.1 26.4": ["habitate"], "6.9 13.4 10.7": ["uncombined"], "11.7 22.4 14.3": ["unsharp"], "8.0 3.6 12.6": ["goating"], "14.8 12.3 27.2": ["polychaete"], "-3.8 17.6 1.6": ["alaihi"], "10.0 -1.4 -1.8": ["disinfectors"], "7.9 26.1 13.0": ["outscrap"], "11.3 6.0 3.9": ["whiparound"], "8.3 -3.8 7.4": ["mundan"], "9.1 16.6 1.6": ["microcurie"], "14.6 3.9 10.6": ["glamourpusses"], "10.7 3.7 -0.8": ["oiland"], "3.8 8.6 18.4": ["marna"], "13.2 11.7 22.1": ["geophagy"], "18.1 9.7 19.9": ["handwarmer"], "3.9 6.2 16.1": ["ibinigay"], "8.5 10.9 19.8": ["flota"], "-3.1 -0.5 3.4": ["enue"], "3.7 1.1 6.7": ["afin"], "3.1 4.4 4.1": ["infructous"], "4.7 6.0 2.3": ["nanopharmaceutical"], "-1.2 15.0 6.4": ["fitly"], "13.2 8.3 6.1": ["unshuttered"], "14.2 2.8 32.5": ["gungo"], "8.3 7.6 31.8": ["underfishing"], "1.7 21.3 2.4": ["exhorter"], "-4.4 16.7 14.3": ["enactor"], "-1.2 6.8 14.8": ["ibalik"], "5.9 10.3 6.4": ["enlargeable"], "2.4 -5.2 5.2": ["stef"], "5.7 3.5 1.0": ["meira"], "12.9 7.2 17.3": ["jayhawk"], "15.6 23.6 13.9": ["dumdum"], "15.5 9.9 13.5": ["hexagonally"], "11.7 2.7 9.0": ["infoworld"], "15.6 -4.2 5.0": ["monogramed"], "5.6 4.9 12.5": ["primeras"], "-5.9 6.0 0.9": ["recevier"], "14.1 11.8 19.2": ["tinglingly"], "4.4 8.0 10.6": ["ibni"], "19.0 13.7 16.3": ["passant"], "15.5 11.7 41.2": ["bolete"], "1.9 10.4 1.7": ["adhesively"], "-5.4 2.4 7.5": ["andassumptions"], "1.9 -0.2 4.2": ["rihk"], "17.0 15.2 11.6": ["skirled"], "-3.5 4.9 3.7": ["electroconvulsive"], "5.5 4.6 8.8": ["microenvironmental"], "14.1 6.5 5.6": ["adelphia"], "13.7 26.6 11.5": ["daimon"], "6.9 20.9 10.3": ["corrup"], "-2.1 2.4 2.2": ["tachycardias"], "16.0 5.0 -0.3": ["emocion"], "-0.2 5.8 7.4": ["natanggap"], "21.1 9.0 10.9": ["tmsuk"], "3.7 0.3 0.3": ["semiprofessionally"], "-2.1 13.0 6.9": ["burgdorferi"], "0.8 24.2 12.9": ["refl"], "7.7 13.8 16.5": ["yooo"], "-2.9 17.0 7.2": ["intraparenchymal"], "17.9 16.2 21.1": ["ponging"], "10.2 0.8 10.0": ["restruct"], "4.5 11.3 2.2": ["mystifier"], "-0.2 -2.2 11.9": ["istess"], "6.7 5.4 9.5": ["nucleobase"], "4.7 -4.4 2.3": ["ecash"], "14.6 -1.2 9.5": ["seum"], "6.2 3.0 7.9": ["ballo"], "8.8 10.5 1.4": ["nonprosecution"], "-1.6 11.0 12.6": ["xcept"], "-2.6 5.6 -0.8": ["codecision"], "-0.6 -3.0 -0.6": ["tative"], "-2.9 13.1 4.3": ["jailable"], "5.9 9.1 1.6": ["earthlink"], "11.0 13.6 15.9": ["krn"], "-4.0 -1.2 -4.7": ["kamala"], "8.8 3.6 0.1": ["psycholinguistic"], "-10.0 2.8 1.7": ["alem"], "1.1 11.0 11.1": ["mesothelial"], "1.8 -3.3 -0.4": ["ifp"], "21.9 17.8 25.1": ["jerboa"], "12.7 2.1 12.2": ["sheetlet"], "-9.2 2.2 -1.5": ["jschulmansr"], "-3.8 5.9 11.1": ["meunier"], "8.8 13.6 11.3": ["bogglingly"], "8.6 4.9 7.5": ["portefeuille"], "4.7 1.3 19.3": ["divaricata"], "2.8 6.6 11.3": ["rappa"], "0.2 14.3 7.0": ["impres"], "7.2 6.2 8.3": ["interfax"], "-0.7 5.3 14.4": ["oners"], "1.3 7.8 22.7": ["cariogenic"], "11.1 2.6 13.4": ["sica"], "10.0 16.2 10.0": ["gaffa"], "6.2 3.2 4.0": ["injurer"], "-2.0 5.8 14.4": ["subseqent"], "9.7 6.6 12.4": ["lipidoid"], "8.6 21.4 -4.1": ["tankbusters"], "-6.7 -0.9 6.7": ["erage"], "21.0 4.4 22.4": ["sauropodomorph"], "15.3 7.7 12.8": ["tildes"], "4.4 7.1 22.3": ["putea"], "-1.0 9.3 11.9": ["turgor"], "1.4 4.8 18.4": ["extrudable"], "11.1 7.2 18.2": ["carbonizing"], "2.8 -0.8 15.9": ["shick"], "-3.6 8.0 15.8": ["dalhin"], "0.1 7.5 5.2": ["gulli"], "13.9 3.1 8.6": ["filiales"], "-9.2 -5.4 2.0": ["compensa"], "-4.0 2.8 1.2": ["multisystemic"], "-2.3 -2.0 -3.7": ["rington"], "0.9 7.8 -2.9": ["trihydrate"], "6.5 1.1 28.3": ["sarson"], "14.3 6.2 6.2": ["comunicado"], "2.2 7.2 11.9": ["nonmenthol"], "15.1 1.9 8.1": ["prototyper"], "-0.5 1.0 13.3": ["posibilidad"], "9.0 16.5 28.1": ["tarsalis"], "-4.7 11.4 1.7": ["glucosidase"], "8.9 3.5 20.5": ["kuttu"], "-7.1 0.5 0.5": ["stealings"], "-8.0 11.0 4.0": ["inforcement"], "3.8 -4.3 3.8": ["epg"], "11.4 13.6 2.4": ["podcatching"], "9.6 12.6 18.1": ["undescended"], "11.0 12.1 10.9": ["ponged"], "-4.5 -1.2 7.7": ["calme"], "31.0 4.7 12.1": ["bobbleheaded"], "1.1 2.7 10.7": ["emilio"], "0.1 5.9 16.0": ["binigay"], "2.0 9.9 8.8": ["intercourses"], "8.1 10.7 12.7": ["mhg"], "6.0 2.0 10.1": ["wereld"], "6.5 11.2 20.2": ["sapat"], "0.2 5.4 -2.3": ["antidiabetes"], "4.1 -7.4 12.3": ["gadael"], "-4.5 4.1 18.5": ["demineralised"], "3.3 -2.5 28.2": ["vinho"], "1.5 13.2 5.5": ["neovascularisation"], "10.3 13.8 6.8": ["electroretinography"], "18.8 -4.9 12.0": ["uilleann"], "5.8 26.8 8.7": ["shifta"], "12.1 13.3 32.9": ["mignons"], "2.2 9.7 13.9": ["biometeorology"], "-0.7 7.1 6.3": ["trophoblastic"], "8.4 23.0 4.6": ["muzhik"], "7.9 5.9 2.4": ["anonyme"], "13.9 0.2 17.3": ["tuart"], "-0.4 -6.1 8.9": ["mainte"], "7.4 3.4 12.7": ["recombinantly"], "3.6 4.4 7.4": ["noro"], "-7.6 1.7 12.7": ["programang"], "-3.0 4.1 9.8": ["hexyl"], "1.7 9.4 3.9": ["stenotype"], "0.1 4.2 6.6": ["romantica"], "-23.7 -4.0 4.7": ["coordi"], "9.5 8.3 36.4": ["bluewing"], "9.5 -3.2 10.5": ["registre"], "-4.3 2.5 5.6": ["noshow"], "8.7 13.7 17.6": ["lakshmiregu"], "4.2 7.1 7.2": ["vanadate"], "4.4 13.8 9.1": ["dritten"], "12.1 7.2 15.0": ["kissathon"], "12.6 -0.2 33.4": ["carciofi"], "8.3 4.0 11.9": ["arthroscopes"], "3.9 13.1 11.4": ["aceshowbiz"], "-6.3 -4.5 -4.0": ["eslicarbazepine"], "9.0 8.5 10.2": ["breaked"], "7.5 5.7 11.0": ["notizia"], "2.7 -2.6 5.5": ["onic"], "7.5 10.4 23.9": ["jamuns"], "-0.0 8.8 -0.1": ["imexon"], "9.3 5.6 14.6": ["salwaar"], "1.9 6.3 5.0": ["suffit"], "1.7 3.8 17.3": ["peshwari"], "7.5 -1.6 -7.1": ["monospaced"], "6.5 6.0 12.7": ["zn"], "13.2 8.4 18.7": ["spazio"], "-1.7 21.1 13.6": ["semites"], "-0.5 11.0 6.5": ["chaim"], "13.0 -2.5 13.3": ["blackstrap"], "0.6 1.2 6.5": ["deserializers"], "-7.6 5.9 7.1": ["paraprotein"], "23.1 14.2 22.0": ["daisylike"], "13.5 22.7 14.8": ["waggers"], "6.6 10.2 16.3": ["ramage"], "-1.3 -0.1 8.0": ["winterball"], "5.8 5.3 12.0": ["morago"], "4.4 12.0 10.1": ["amchi"], "16.6 6.2 11.0": ["dacks"], "19.6 13.7 15.2": ["sportscoats"], "3.9 -1.7 9.8": ["arweinydd"], "-2.5 -3.4 0.7": ["stelle"], "3.8 -0.7 13.5": ["ribonucleotide"], "13.4 9.0 32.7": ["pistache"], "16.5 8.7 22.7": ["gaters"], "14.6 1.9 -0.9": ["activebank"], "11.0 4.2 22.2": ["sigatoka"], "-2.5 -5.9 7.0": ["specifica"], "0.8 6.0 15.0": ["interesterified"], "4.3 18.1 2.9": ["deflectable"], "5.4 6.9 6.6": ["toolmark"], "2.7 -1.2 8.2": ["offiscal"], "15.4 3.9 32.6": ["lato"], "-3.9 9.6 7.2": ["gled"], "7.0 10.7 8.0": ["mto"], "6.6 2.6 14.2": ["jij"], "5.8 8.9 23.2": ["nooners"], "9.4 -2.9 16.1": ["jugo"], "7.0 14.7 11.4": ["absoluta"], "-1.2 3.2 2.8": ["checkereds"], "18.0 10.2 15.6": ["whammied"], "9.6 -1.1 7.9": ["microderm"], "-0.2 6.7 10.5": ["sulphosalts"], "5.7 17.2 5.8": ["celebral"], "10.0 9.3 9.0": ["sartorialist"], "6.3 3.9 29.9": ["inshell"], "-3.8 -12.7 5.7": ["pahs"], "1.7 18.8 6.6": ["outjabbed"], "5.9 6.3 13.1": ["styptic"], "17.9 13.8 7.6": ["oreilly"], "10.4 -0.4 15.1": ["subtilisin"], "0.7 2.2 -2.7": ["enfance"], "6.4 21.4 20.4": ["indeedy"], "0.8 1.2 6.5": ["signifi"], "-1.9 4.9 1.8": ["sofort"], "19.4 8.4 16.1": ["clamdigger"], "12.8 5.9 15.6": ["fuoco"], "1.1 2.9 17.2": ["mahalaga"], "4.4 10.4 6.4": ["takingly"], "10.3 18.6 4.8": ["fruitloops"], "3.0 20.5 -1.5": ["ticketable"], "5.4 12.2 7.1": ["geste"], "2.5 17.9 11.6": ["walon"], "1.3 -3.2 11.5": ["vache"], "3.5 -5.1 -5.9": ["worx"], "4.3 7.2 8.6": ["evolver"], "-1.0 11.2 19.5": ["harap"], "8.8 12.2 18.7": ["casei"], "17.5 12.5 22.2": ["hippity"], "2.3 1.4 10.6": ["ymosodiad"], "17.5 13.9 16.9": ["rainnwilson"], "9.6 -6.8 28.7": ["buco"], "3.4 -0.9 5.7": ["packag"], "0.2 16.6 0.1": ["storying"], "6.6 17.8 13.1": ["fungoides"], "9.0 6.2 5.6": ["mdl"], "3.8 12.6 15.9": ["cumplir"], "5.9 3.0 5.5": ["empleo"], "9.8 8.2 8.9": ["troit"], "3.1 -1.4 6.9": ["drv"], "8.7 12.0 35.8": ["westslope"], "-7.6 2.9 6.6": ["pating"], "-2.8 -4.8 -0.0": ["ecm"], "2.1 2.5 12.8": ["lentigines"], "16.2 0.4 13.0": ["tutta"], "-1.8 -1.8 -0.2": ["medoxomil"], "13.6 -0.6 15.9": ["biloba"], "21.2 16.8 17.5": ["frogged"], "11.9 20.2 43.8": ["ratz"], "3.6 21.9 4.5": ["unhealable"], "4.4 5.3 4.8": ["roadtested"], "3.2 4.0 8.1": ["topworkplaces"], "19.1 6.0 24.1": ["earred"], "-3.4 -5.3 -1.6": ["hoteles"], "-2.0 4.4 14.4": ["cryptococcus"], "5.3 -1.3 2.0": ["eria"], "7.1 3.3 11.5": ["slechts"], "12.2 7.0 7.1": ["splurgers"], "4.5 9.6 15.0": ["tengan"], "1.3 -3.2 4.0": ["uled"], "0.0 -5.1 2.8": ["interswitch"], "0.8 6.6 -0.9": ["ghostwrites"], "-3.8 3.9 6.3": ["milna"], "12.2 9.0 24.3": ["pipal"], "-13.1 -0.7 -3.9": ["ael"], "8.7 11.5 10.9": ["buque"], "13.2 6.2 8.6": ["clubsport"], "18.9 11.4 19.3": ["citement"], "9.7 12.5 8.6": ["adgrunts"], "5.9 10.4 12.7": ["crushworthy"], "5.5 4.8 -1.2": ["polyethersulfone"], "1.3 5.8 19.0": ["papunta"], "1.9 9.6 13.4": ["scabrously"], "4.0 17.0 10.4": ["habitude"], "-0.7 -5.8 -0.8": ["energystar"], "9.9 12.2 8.5": ["saturable"], "0.8 7.2 17.0": ["ahensya"], "18.5 22.8 6.9": ["nonsecret"], "9.1 1.6 13.9": ["toegevoegd"], "8.2 6.1 -0.3": ["metasystem"], "2.6 4.8 11.7": ["mambabatas"], "7.2 1.6 4.6": ["nifer"], "1.5 -0.7 -3.1": ["mesilate"], "5.0 0.5 1.2": ["metalwoods"], "-7.4 8.3 -0.8": ["etats"], "-0.4 -10.7 9.5": ["hyatt"], "9.6 12.8 4.3": ["condomless"], "3.2 13.9 2.4": ["rtsp"], "17.1 -2.1 8.2": ["jiggery"], "4.3 9.7 7.9": ["pamby"], "7.7 11.0 6.3": ["bloqueo"], "17.2 0.3 35.6": ["bagna"], "2.9 -1.0 6.2": ["allega"], "13.4 3.5 8.9": ["whollyowned"], "6.7 19.7 20.9": ["juliflora"], "13.3 5.6 13.2": ["pallidus"], "12.0 -5.5 10.5": ["sheung"], "6.3 1.5 4.1": ["zhoo"], "4.5 -4.2 -1.8": ["sembly"], "16.2 4.5 12.1": ["synclinal"], "4.5 0.3 7.6": ["cifra"], "2.5 1.2 16.4": ["chauth"], "-7.7 2.7 -2.7": ["pudendal"], "7.2 4.1 -0.7": ["rodless"], "10.9 18.8 13.3": ["cogito"], "11.0 14.0 9.7": ["unconformable"], "12.5 9.9 16.3": ["grandchidren"], "8.1 3.8 20.1": ["glovers"], "-2.9 4.0 13.1": ["intertrochanteric"], "15.7 11.7 11.2": ["alpargatas"], "-4.3 6.0 3.7": ["gious"], "2.4 -0.6 2.5": ["noviembre"], "9.9 8.8 4.6": ["officieel"], "3.2 3.0 8.0": ["delos"], "15.1 4.2 8.8": ["taliglucerase"], "1.4 0.7 11.8": ["duran"], "19.0 6.4 11.5": ["steampipe"], "9.9 9.0 10.8": ["referencia"], "1.8 2.0 3.4": ["caprotec"], "5.2 6.4 44.0": ["scalefish"], "-4.2 -0.3 5.3": ["treh"], "-2.5 -2.6 0.5": ["rquez"], "-4.3 11.4 10.4": ["predistortion"], "-3.9 0.0 12.9": ["contem"], "9.9 1.1 21.3": ["colloform"], "2.1 10.1 12.1": ["jaadu"], "2.2 0.9 -0.2": ["easypod"], "-4.5 -1.2 -7.7": ["supraventricular"], "-2.6 6.0 2.6": ["urography"], "6.9 17.7 3.6": ["rapest"], "2.6 4.7 18.9": ["madrina"], "6.2 -5.3 11.8": ["dibasic"], "1.9 -1.9 3.4": ["cision"], "5.5 -3.7 -4.8": ["curasan"], "-2.1 1.0 4.2": ["hyperproliferative"], "14.6 22.7 0.2": ["forfend"], "6.5 12.5 0.2": ["vivendi"], "1.3 1.9 6.7": ["meinen"], "-0.2 11.0 6.5": ["poten"], "13.0 8.6 12.6": ["hydroxymethylfurfural"], "2.9 20.0 15.6": ["fosimmons"], "11.6 2.9 22.3": ["batatas"], "-0.3 12.0 6.0": ["nagsabi"], "5.0 -0.4 7.2": ["lancearmstrong"], "13.4 -4.1 -7.4": ["immedia"], "-6.0 0.3 1.4": ["diammonium"], "3.2 -4.3 2.9": ["tetrachloride"], "3.4 -2.0 5.4": ["tability"], "4.9 9.3 -0.7": ["perseverative"], "6.2 13.1 11.4": ["jadu"], "9.7 1.2 12.5": ["poom"], "4.9 13.0 7.9": ["nonspousal"], "19.4 27.1 11.3": ["vasty"], "17.0 18.0 17.5": ["samoan"], "2.2 4.0 5.4": ["cago"], "4.9 11.7 8.8": ["soledad"], "0.2 15.6 15.7": ["nonwaiver"], "1.9 2.4 -4.8": ["qualifi"], "7.3 8.5 12.1": ["anaphylactoid"], "-3.1 -5.4 -10.6": ["senting"], "5.5 6.5 6.7": ["chrisbrown"], "-5.1 2.8 8.4": ["dcr"], "9.5 8.9 41.6": ["turnstone"], "8.6 7.6 10.6": ["monna"], "19.3 4.2 35.1": ["wantan"], "8.3 -0.0 20.3": ["gures"], "12.4 13.5 16.2": ["hellified"], "2.5 6.5 -0.8": ["acknowl"], "8.3 -0.1 14.8": ["zaito"], "7.7 0.7 7.0": ["cierre"], "10.3 3.4 7.6": ["totalisation"], "8.7 3.7 13.6": ["godi"], "5.8 4.0 25.8": ["furtaker"], "-0.6 -7.9 10.0": ["nspc"], "6.3 -1.0 12.0": ["sahr"], "-6.5 -7.9 6.4": ["coursetakers"], "9.6 4.8 0.7": ["netwo"], "1.3 8.0 6.1": ["velt"], "-15.1 -0.9 -6.5": ["coordiantor"], "3.8 20.3 9.0": ["vencido"], "6.0 4.0 5.7": ["extraocular"], "-6.5 5.1 9.6": ["nagbigay"], "10.4 0.0 13.6": ["ziet"], "8.5 3.9 1.6": ["rojects"], "10.1 -3.5 5.1": ["unbadged"], "-8.3 2.0 -3.7": ["ority"], "9.8 2.1 26.4": ["gandules"], "3.6 0.2 10.8": ["jdbc"], "0.9 6.9 10.9": ["certaine"], "2.1 12.4 17.1": ["jaata"], "-0.2 9.9 16.4": ["mesial"], "0.4 -5.4 6.5": ["controllata"], "3.0 3.7 4.9": ["behandelt"], "15.6 1.2 5.9": ["ondersteuning"], "2.5 24.4 5.1": ["lietenant"], "14.9 11.0 15.7": ["lickety"], "2.3 15.3 14.2": ["mntkm"], "1.7 1.8 9.1": ["radyo"], "10.2 2.8 7.7": ["tenido"], "6.7 3.3 14.8": ["teds"], "14.4 16.8 17.0": ["petewentz"], "10.8 9.4 12.7": ["perfluorooctane"], "6.3 9.0 14.1": ["hakuna"], "-0.8 13.4 3.6": ["shabaab"], "14.2 -1.2 12.6": ["rompin"], "-0.5 -3.2 -4.1": ["compro"], "12.0 5.0 21.0": ["purpureum"], "-0.7 16.3 9.1": ["outfi"], "8.4 16.5 20.6": ["ladino"], "-2.1 0.4 14.0": ["oncoplastic"], "1.4 0.4 15.7": ["preme"], "8.6 12.3 26.1": ["berrylike"], "15.3 12.6 21.6": ["bullrope"], "14.0 4.9 4.4": ["oficina"], "6.4 -9.9 -0.6": ["merce"], "0.5 -2.2 1.6": ["sportifs"], "2.4 12.3 -0.7": ["thinkpiece"], "13.1 -6.4 -0.2": ["embedders"], "3.1 1.2 7.2": ["maldigestion"], "-2.0 3.7 16.2": ["aaral"], "2.3 11.1 7.2": ["aankhon"], "4.0 10.3 12.0": ["haberin"], "5.3 7.5 20.5": ["ployment"], "9.6 4.6 9.0": ["keygens"], "1.5 -11.1 -7.8": ["casestudies"], "-1.2 -3.7 -3.4": ["wkms"], "14.0 6.0 3.8": ["tomor"], "4.3 3.0 10.3": ["astromaterials"], "7.0 15.3 18.3": ["mazal"], "-4.5 13.4 7.7": ["nities"], "19.7 19.2 4.3": ["unbusiness"], "13.1 6.3 6.2": ["primion"], "10.1 10.1 16.3": ["multicelled"], "4.0 -5.5 19.6": ["tuberosum"], "8.2 0.2 0.5": ["gayed"], "13.9 4.9 26.3": ["tiare"], "-10.1 -7.6 13.3": ["mester"], "-3.5 10.7 -2.9": ["trangendered"], "19.1 7.1 21.4": ["poka"], "1.1 -3.3 6.5": ["skuh"], "-3.1 -6.4 1.4": ["fgi"], "21.5 5.8 16.9": ["icerink"], "5.9 10.0 15.7": ["salama"], "10.5 8.3 12.3": ["sutherland"], "11.4 15.9 7.5": ["gloire"], "11.0 8.4 7.2": ["bibanja"], "-0.3 4.7 -1.7": ["arbaclofen"], "2.8 -6.1 4.5": ["elopment"], "-3.4 -2.0 2.0": ["pandemicflu"], "6.2 13.1 2.2": ["farwestern"], "8.9 11.1 15.8": ["megacolon"], "11.9 3.8 10.8": ["isomerisation"], "1.7 5.4 15.1": ["dilantin"], "-9.3 -1.4 1.5": ["uate"], "1.1 -5.3 7.3": ["kuhs"], "-4.7 24.9 -1.8": ["hrer"], "8.7 0.0 13.6": ["amoureux"], "4.1 3.9 3.2": ["connec"], "2.1 7.3 15.1": ["eggaday"], "-1.8 -0.3 -0.6": ["gible"], "5.9 5.1 15.3": ["dzi"], "15.2 1.2 9.3": ["claddagh"], "2.8 -2.4 -5.8": ["tensive"], "13.7 1.7 -0.1": ["nonprofessionally"], "2.7 -2.2 5.2": ["tinue"], "-4.8 -8.8 0.9": ["tourna"], "5.2 14.9 11.3": ["oxyhydrogen"], "2.4 3.6 11.4": ["dyschromia"], "4.5 18.2 -1.8": ["portaying"], "-4.5 2.7 7.6": ["provera"], "13.4 3.1 27.3": ["mydas"], "11.1 6.0 19.1": ["tagua"], "5.0 -0.6 -0.5": ["applicat"], "7.4 12.0 10.6": ["sniffable"], "24.9 12.5 30.0": ["pepo"], "-6.1 -6.5 -3.6": ["ditional"], "-1.5 3.3 8.3": ["tropicalis"], "15.3 7.9 20.4": ["brickle"], "-1.2 1.7 5.5": ["paronychia"], "12.1 -3.1 9.5": ["bancaire"], "1.4 5.6 -1.4": ["nancing"], "6.0 -2.3 3.7": ["coflex"], "9.6 1.4 17.5": ["swillin"], "9.5 -0.8 23.2": ["lazuli"], "8.6 11.8 27.5": ["furtaking"], "6.5 8.3 15.6": ["snowsquall"], "-7.5 12.1 8.0": ["nonhomicide"], "6.3 31.2 9.5": ["kassam"], "0.1 5.2 4.8": ["newstalk"], "11.6 9.0 8.3": ["carnivallike"], "-5.7 5.1 11.7": ["imigrant"], "3.4 7.4 4.5": ["piri"], "10.9 12.8 17.1": ["drews"], "2.2 1.0 11.1": ["wung"], "8.8 28.7 8.6": ["semicolonial"], "7.0 7.4 17.9": ["dumaan"], "18.2 8.2 19.7": ["oriel"], "12.7 5.7 3.1": ["pokery"], "3.3 0.3 4.9": ["electrolytically"], "16.6 25.7 14.5": ["retardent"], "8.0 1.2 -0.4": ["bodypack"], "-5.2 1.9 -1.4": ["ament"], "7.1 14.2 3.9": ["trueblue"], "1.1 1.6 7.9": ["metatarsophalangeal"], "10.8 1.9 15.2": ["tosa"], "-3.6 1.5 -3.5": ["structor"], "-6.2 3.5 10.3": ["zul"], "-2.0 10.6 7.4": ["onship"], "3.7 6.3 11.3": ["poquito"], "2.3 2.4 12.1": ["miei"], "4.8 2.3 3.1": ["ankylosing"], "4.0 4.9 12.9": ["noires"], "10.1 -0.5 9.7": ["discon"], "10.6 3.6 13.3": ["dichromate"], "9.7 5.9 6.7": ["bilt"], "12.3 8.1 23.6": ["scapularis"], "7.7 10.1 15.8": ["maycause"], "7.5 6.2 7.1": ["mammillary"], "-7.1 17.3 -3.0": ["membering"], "9.7 -4.0 5.0": ["multicontour"], "25.7 -3.9 17.8": ["sulcata"], "1.5 4.2 8.9": ["tists"], "-0.3 6.0 1.8": ["gihn"], "5.1 10.5 17.4": ["centros"], "8.2 6.8 5.0": ["acquisto"], "-1.4 20.9 1.5": ["offesive"], "17.6 -1.7 18.7": ["lucida"], "13.6 -2.5 19.3": ["peking"], "6.7 3.0 11.5": ["karva"], "11.6 20.8 18.9": ["cussers"], "18.3 8.1 28.3": ["glub"], "4.9 5.6 13.3": ["oiseau"], "-5.3 9.0 10.0": ["sicca"], "9.6 16.9 19.9": ["yabba"], "-7.1 10.1 3.7": ["officeholding"], "-3.8 -2.0 14.5": ["makapasok"], "13.0 6.0 17.4": ["pensar"], "4.3 -4.6 3.7": ["restau"], "5.5 3.7 23.8": ["khash"], "18.0 -1.7 18.9": ["overproof"], "-8.1 8.4 4.6": ["situa"], "0.9 1.9 4.8": ["publicaffairs"], "8.5 -2.3 12.5": ["peye"], "7.9 2.7 5.4": ["thevillage"], "8.4 -2.7 0.3": ["expecta"], "-8.1 -1.8 6.5": ["transcervical"], "7.8 17.9 7.8": ["referentiality"], "7.8 1.9 26.3": ["happi"], "2.7 15.6 12.1": ["intraepithelial"], "4.2 2.6 13.6": ["cous"], "1.8 14.5 16.5": ["voti"], "0.4 15.0 11.5": ["estray"], "5.8 4.1 13.1": ["naturaleza"], "10.4 -4.0 9.6": ["baisse"], "12.1 5.4 8.4": ["cardan"], "7.6 -5.6 0.9": ["companying"], "4.1 -8.9 2.6": ["maleic"], "8.1 -0.7 17.7": ["gastronomist"], "6.7 7.7 20.7": ["nigrum"], "5.6 -7.1 12.7": ["luhs"], "8.2 12.2 13.9": ["smok"], "5.9 2.9 10.5": ["ophiolitic"], "15.1 8.0 15.8": ["acidulated"], "5.0 6.4 20.6": ["limoncellos"], "-2.7 -8.5 5.1": ["onlineservices"], "19.9 13.3 5.8": ["sandswept"], "-1.4 7.4 15.1": ["bersanding"], "5.7 6.7 -5.1": ["sterreich"], "10.4 13.7 9.4": ["gte"], "-0.5 7.7 -6.6": ["endoplasmic"], "27.4 21.4 23.1": ["punji"], "14.9 15.3 3.9": ["phoenixlike"], "10.2 14.4 13.0": ["dilithium"], "4.7 -0.3 5.9": ["ursday"], "9.9 7.9 4.0": ["gazza"], "5.8 -1.2 -15.3": ["technik"], "6.1 1.5 27.8": ["bors"], "15.7 9.4 26.1": ["wakas"], "8.0 14.1 17.1": ["labrusca"], "0.6 13.9 9.0": ["chahte"], "13.6 0.4 7.2": ["sweaterdresses"], "8.3 -4.8 1.5": ["terza"], "9.9 8.5 15.2": ["epidemically"], "4.0 23.1 15.9": ["seismologically"], "-2.6 1.8 5.7": ["aldactone"], "-7.0 8.6 10.8": ["toz"], "2.7 18.3 5.2": ["voiceprinting"], "7.6 -15.8 -2.6": ["abilia"], "0.8 5.9 13.2": ["competititors"], "10.2 13.2 12.6": ["bargining"], "1.1 -6.7 8.1": ["uing"], "12.9 9.5 20.1": ["curliest"], "5.0 9.7 3.3": ["magnetotellurics"], "-1.3 4.9 13.9": ["bbn"], "-6.2 1.6 9.1": ["neys"], "1.7 1.9 1.5": ["bage"], "-1.1 10.5 8.4": ["extrait"], "-3.9 2.7 8.1": ["sirah"], "1.2 14.5 6.5": ["apost"], "2.3 1.6 10.3": ["openldap"], "4.2 1.9 15.2": ["ghaghra"], "4.8 5.3 7.0": ["hawai"], "18.1 4.0 5.6": ["twiddlers"], "-0.0 14.1 14.4": ["hees"], "6.2 -1.8 10.0": ["cheape"], "8.5 6.3 4.7": ["equivalized"], "2.5 -1.2 1.6": ["includiing"], "2.0 9.9 25.5": ["masak"], "0.7 4.9 15.9": ["interbasin"], "5.1 26.7 9.2": ["deadspace"], "0.3 7.0 11.8": ["buchanan"], "0.8 -2.1 15.3": ["hunga"], "7.3 5.0 13.9": ["consiste"], "12.2 10.4 23.6": ["kousa"], "-3.6 7.6 15.4": ["kek"], "10.8 9.1 11.1": ["consecuencia"], "0.6 4.7 11.3": ["llegada"], "-1.6 -2.6 -2.8": ["directeurs"], "-2.7 6.4 7.6": ["betes"], "-4.2 -4.2 9.6": ["powerskating"], "1.8 3.4 16.4": ["mances"], "3.6 14.3 15.6": ["phyiscally"], "7.3 5.4 9.5": ["chlamydiosis"], "-1.3 2.4 5.7": ["rected"], "20.3 15.4 22.4": ["cleating"], "18.9 16.2 34.5": ["yellowhead"], "7.6 8.8 1.5": ["sportswagon"], "3.8 11.9 16.2": ["alaskitic"], "8.5 -0.5 13.4": ["celine"], "7.1 4.8 8.8": ["beauti"], "3.5 4.8 -0.5": ["fasciculus"], "9.6 2.5 11.7": ["actinin"], "1.2 -1.1 13.8": ["elimina"], "1.6 20.1 16.5": ["keating"], "-0.3 8.6 2.9": ["phorbol"], "4.6 2.3 14.5": ["departamento"], "-1.5 4.2 13.7": ["sumali"], "12.5 17.7 17.1": ["furiosus"], "17.3 7.5 15.1": ["wicky"], "10.9 13.2 14.6": ["rescate"], "8.2 3.3 5.7": ["sanitaire"], "9.1 4.1 35.7": ["camaron"], "17.3 11.9 37.7": ["jjigae"], "0.2 7.3 -9.9": ["thromboemboli"], "9.9 8.7 7.2": ["halen"], "6.4 2.9 13.3": ["hanafuda"], "13.8 7.7 10.9": ["mesospheric"], "6.6 11.2 5.6": ["thoracoscope"], "4.9 0.5 13.8": ["wynebu"], "3.3 19.8 4.2": ["stellacure"], "6.4 3.6 22.8": ["mellifera"], "-0.8 6.1 13.2": ["awg"], "10.4 1.4 12.2": ["accordo"], "21.0 18.0 2.1": ["camphones"], "8.2 -7.5 -9.1": ["bauen"], "-5.0 3.8 11.0": ["septiembre"], "-3.2 -5.5 10.3": ["geoarchaeologist"], "-1.3 -2.6 5.5": ["joung"], "8.4 -3.1 2.4": ["trik"], "16.5 16.5 35.1": ["chinkapin"], "-2.3 4.6 5.8": ["suvidha"], "1.4 -8.1 -2.6": ["corporateresponsibility"], "4.9 5.6 13.2": ["castile"], "6.6 4.1 8.2": ["skyped"], "5.0 8.4 9.5": ["hypervascular"], "1.0 7.4 1.8": ["indepen"], "-1.5 18.9 3.3": ["lankans"], "9.6 12.0 5.1": ["habeus"], "0.4 1.2 13.5": ["farwolaeth"], "0.6 0.5 3.1": ["besifloxacin"], "14.3 12.8 23.2": ["orbicular"], "1.7 8.8 15.0": ["altura"], "11.5 6.9 0.2": ["rmg"], "7.6 14.8 18.0": ["bollinger"], "-3.3 4.3 8.2": ["sulfadiazine"], "-3.0 10.5 6.7": ["absurdum"], "16.3 -0.7 -3.3": ["skoool"], "6.0 -5.9 4.6": ["monogastric"], "2.3 3.8 4.1": ["retaspimycin"], "6.7 1.5 14.9": ["dweud"], "9.7 15.9 19.8": ["sanguineum"], "2.5 6.2 3.2": ["aquellos"], "7.8 22.1 4.4": ["hamednz"], "12.7 9.6 3.4": ["enhacing"], "12.0 3.6 10.1": ["sylvania"], "5.6 2.7 17.0": ["natapos"], "9.1 19.7 13.0": ["gilli"], "3.8 11.9 10.4": ["penhold"], "3.5 0.7 9.7": ["tck"], "-3.5 1.8 2.5": ["ngor"], "15.3 7.2 3.9": ["ebration"], "9.8 5.7 27.9": ["blackpoll"], "7.8 13.0 15.8": ["ichimoku"], "17.3 27.3 7.9": ["hellstorm"], "-1.6 -5.0 3.6": ["trative"], "1.8 9.7 27.9": ["salan"], "7.5 -3.3 4.8": ["alimentos"], "-2.1 3.5 1.6": ["litem"], "11.7 -9.6 7.9": ["farw"], "17.9 -4.0 19.2": ["guipure"], "9.1 6.3 24.4": ["argy"], "-3.8 3.0 15.2": ["diumano"], "13.7 3.0 7.8": ["hypoglycemics"], "4.8 0.7 9.6": ["culti"], "0.3 11.8 8.5": ["carcinomatosis"], "8.9 1.4 19.6": ["oeurves"], "-1.8 -6.3 7.2": ["fullday"], "11.2 -1.3 -2.7": ["softwa"], "0.4 7.9 1.5": ["suprema"], "-7.3 5.6 -2.0": ["withoutlimitation"], "15.0 -7.2 2.5": ["stlg"], "14.6 12.2 16.5": ["zom"], "-1.0 12.0 15.1": ["maculopapular"], "5.0 11.4 15.4": ["iure"], "-2.4 7.2 12.1": ["huhs"], "8.7 16.9 6.4": ["tsumanis"], "18.9 13.1 20.9": ["blankety"], "-0.5 14.9 15.1": ["frus"], "-5.0 -2.4 3.4": ["culturelles"], "8.6 12.4 17.6": ["syringae"], "9.6 4.1 7.8": ["supergravity"], "3.0 11.9 9.1": ["knowl"], "0.3 6.9 -2.4": ["oxygenase"], "1.9 3.3 8.3": ["capsulitis"], "-5.5 10.9 -5.2": ["analaysis"], "-3.3 -2.9 3.1": ["neurotology"], "1.7 9.6 8.7": ["quired"], "-1.1 10.7 -0.9": ["isf"], "0.0 -0.8 7.8": ["fluorimetric"], "0.6 5.2 3.7": ["dynadock"], "-1.0 -3.1 6.4": ["reticulin"], "10.0 0.5 2.9": ["smoothwall"], "8.1 -4.9 0.3": ["presentado"], "10.6 8.4 36.2": ["weever"], "9.0 -6.7 20.3": ["spooners"], "4.9 -0.3 6.5": ["tti"], "14.2 9.0 21.7": ["malva"], "7.1 7.3 14.7": ["faucibus"], "8.1 12.9 14.2": ["sooey"], "4.9 -4.6 22.8": ["ceol"], "8.8 5.1 26.9": ["frazil"], "19.1 2.5 17.8": ["sunlike"], "-5.7 10.9 2.3": ["shabelle"], "2.2 4.6 -4.0": ["niverse"], "4.6 14.9 22.8": ["overbrowning"], "0.3 2.1 8.5": ["hydroxyethyl"], "23.7 11.0 16.6": ["carlae"], "14.8 10.8 30.5": ["royales"], "3.6 9.4 -2.8": ["kadhis"], "8.8 6.8 4.0": ["vigah"], "30.7 12.9 28.0": ["darner"], "6.9 -3.3 0.4": ["zhah"], "-9.1 12.9 -0.6": ["chaudhry"], "-7.5 -3.0 7.4": ["vanden"], "13.5 6.4 14.2": ["crosslegged"], "11.5 10.0 16.9": ["frpl"], "4.9 7.0 14.9": ["petechial"], "1.0 -1.2 4.4": ["charcha"], "8.9 -3.3 6.8": ["eering"], "15.8 3.0 6.9": ["tocking"], "15.1 18.2 14.9": ["redock"], "1.1 6.4 13.6": ["matulungan"], "9.3 1.6 13.6": ["cynulliad"], "2.4 7.4 5.5": ["epidermidis"], "17.0 -3.8 20.8": ["cowry"], "0.5 9.6 16.9": ["malleolus"], "2.6 5.1 2.9": ["angiopathy"], "10.2 9.7 16.4": ["gunga"], "-0.6 3.8 0.5": ["enfermedad"], "8.2 8.5 20.8": ["tost"], "16.8 2.5 -1.8": ["roperty"], "-5.2 5.1 18.0": ["muang"], "4.5 7.5 15.3": ["cused"], "2.6 9.6 3.2": ["unlapped"], "7.5 23.5 7.9": ["sacrifce"], "20.6 10.0 23.4": ["caramba"], "9.8 -2.4 20.9": ["paus"], "-9.7 -3.2 2.2": ["vidual"], "0.1 12.3 15.6": ["datta"], "5.9 -8.6 4.6": ["insuran"], "8.4 -1.2 4.2": ["chemogenomic"], "13.0 1.4 4.5": ["cokey"], "-0.6 9.7 3.9": ["butable"], "4.3 5.9 8.3": ["flued"], "9.2 17.0 2.9": ["vory"], "-3.0 7.6 5.2": ["phrenic"], "0.1 2.5 7.8": ["mspc"], "8.8 6.8 13.2": ["bifida"], "7.5 -3.0 7.2": ["acetonide"], "12.2 6.4 26.5": ["viande"], "16.6 14.6 17.5": ["multipaned"], "3.7 5.7 0.7": ["hereunto"], "15.6 1.3 -2.2": ["plynarenska"], "18.0 16.7 27.2": ["chollas"], "9.3 5.4 6.2": ["nisation", "azilsartan"], "7.8 9.0 20.5": ["nicholson"], "3.1 15.4 6.3": ["upi"], "7.5 17.1 11.1": ["superpotent"], "14.4 4.2 11.2": ["nanotubules"], "-0.3 6.4 12.7": ["bryd"], "-2.5 -3.5 -0.4": ["transferases"], "-0.4 0.5 2.1": ["rda"], "4.0 -2.8 14.4": ["divinorum"], "-0.6 -2.3 7.8": ["gannett"], "7.9 11.9 5.2": ["discurso"], "5.9 -1.8 24.9": ["kishmish"], "13.3 -1.1 13.9": ["morpho"], "12.4 15.7 11.7": ["farers"], "2.2 3.9 12.7": ["allura"], "7.3 -0.4 25.5": ["wirebonding"], "11.8 -0.9 33.7": ["leghorns"], "12.7 10.4 8.9": ["gardes"], "0.4 -1.4 11.9": ["apelio"], "3.1 9.4 16.8": ["iain"], "15.1 -1.3 28.2": ["papri"], "3.9 -1.0 11.3": ["gynnal"], "4.5 7.4 12.1": ["tetrasodium"], "4.5 -5.0 6.3": ["ependymal"], "5.5 4.9 3.4": ["resorptive"], "15.9 -0.8 30.2": ["munia"], "6.1 -3.3 -3.6": ["progrm"], "10.4 1.5 4.6": ["microtomography"], "9.8 5.5 10.7": ["testants"], "-0.3 -1.2 1.2": ["entary"], "10.1 9.8 10.4": ["chickendinner"], "18.8 12.0 19.1": ["pumpy"], "1.3 -0.2 12.1": ["bulgaricus"], "-1.0 2.0 10.3": ["dations"], "4.1 8.3 1.7": ["vilanterol"], "13.2 2.6 15.1": ["kneehole"], "3.2 2.7 3.3": ["crohn"], "-0.2 4.7 13.1": ["paliwanag"], "6.7 4.9 4.1": ["antiinfective"], "5.2 1.4 4.2": ["sloot"], "-0.7 -3.9 -1.6": ["associ"], "4.6 3.5 12.0": ["theca"], "-1.3 4.6 5.5": ["proviral"], "7.3 -0.3 7.6": ["jkl"], "-4.4 14.4 8.3": ["noncommunicable"], "4.3 1.2 0.9": ["autochanger"], "-2.4 2.9 19.4": ["ouvres"], "10.3 13.6 9.5": ["brainfreeze"], "-2.9 13.5 5.2": ["ferent"], "3.0 6.7 18.6": ["multisymptom"], "0.7 4.7 4.4": ["autoflex"], "7.2 0.8 3.7": ["plaining"], "-0.2 2.7 6.5": ["tabula"], "17.1 10.1 9.1": ["upstretched"], "3.3 8.4 12.5": ["factured"], "2.7 4.1 -5.1": ["joimax"], "-4.5 1.1 -0.5": ["nty"], "-3.7 1.2 -2.6": ["ahb"], "0.6 -1.6 7.4": ["cuales"], "-11.4 8.7 -3.7": ["carbapenemase"], "2.0 -0.9 8.6": ["salivarius"], "11.0 1.8 18.4": ["fectly"], "2.2 2.9 5.4": ["ranpirnase"], "-5.1 -0.9 6.7": ["globus"], "0.9 8.7 14.8": ["dodi"], "10.4 2.2 19.7": ["hybridus"], "8.1 20.8 24.1": ["funestus"], "7.9 -3.8 10.1": ["objeto"], "4.4 5.8 2.2": ["surro"], "8.8 10.9 10.8": ["veganic"], "16.3 10.1 35.2": ["cockahoes"], "4.9 8.0 -0.0": ["stoy"], "21.3 17.5 8.4": ["photosynth"], "20.0 1.0 7.3": ["clusterf"], "-0.6 0.1 7.8": ["nagpapasalamat"], "11.4 6.9 5.0": ["vatted"], "3.7 6.3 16.1": ["instalaciones"], "-5.3 0.9 4.6": ["nonvertebral"], "7.6 15.2 9.2": ["beddy"], "-2.7 -2.9 -0.3": ["bronchopulmonary"], "3.6 2.9 3.0": ["statut"], "11.6 20.0 11.0": ["batsh"], "4.6 13.6 2.8": ["rajeshsingla"], "18.4 13.7 27.7": ["pucky"], "2.2 1.7 2.3": ["secfilings"], "7.8 9.5 20.5": ["shoers"], "11.5 10.4 18.9": ["blastic"], "-4.7 2.7 10.6": ["oas"], "6.4 8.6 11.0": ["membre"], "-0.5 12.5 5.7": ["finable"], "6.2 -3.3 7.0": ["contratto"], "16.7 5.6 24.8": ["snoose"], "18.2 8.0 31.3": ["aduki"], "5.6 9.1 3.5": ["morphogenic"], "1.3 3.1 6.5": ["ganglionic"], "8.8 -12.7 20.0": ["oosiks"], "11.1 -3.6 26.0": ["tato"], "5.2 17.9 -2.1": ["thethat"], "6.1 -10.5 -0.1": ["teleproduction"], "2.5 2.9 -0.4": ["keratectomy"], "0.8 3.9 7.9": ["renseignements"], "4.4 5.3 18.5": ["temporomandibular"], "13.4 4.7 0.4": ["ivillage"], "-5.5 7.8 8.2": ["suttin"], "13.6 -1.6 13.4": ["rbls"], "14.4 11.9 11.0": ["assless"], "8.1 6.6 14.3": ["gondii"], "7.8 -1.8 15.6": ["chorionic"], "16.5 -1.5 39.0": ["portobella"], "3.1 -3.1 7.2": ["sogno"], "-1.5 -5.2 6.9": ["rectovaginal"], "1.8 6.2 8.3": ["interosseous"], "13.7 5.0 5.6": ["dorma"], "16.6 -0.2 7.8": ["ferris"], "15.8 4.2 3.8": ["livescore"], "1.2 5.4 13.5": ["zachary"], "3.1 3.1 23.3": ["thunbergii"], "12.3 9.1 9.9": ["prepandemic"], "-7.7 22.1 1.4": ["kotwal"], "3.4 5.4 1.8": ["escucha"], "3.9 16.0 6.7": ["manoos"], "19.1 20.7 6.2": ["pentup"], "5.9 11.9 14.9": ["makinga"], "-7.3 -17.3 0.6": ["vitational"], "11.7 8.0 24.7": ["pottie"], "8.4 14.1 7.8": ["shome"], "1.0 1.5 10.2": ["scritto"], "2.3 7.9 13.0": ["kagaya"], "4.6 5.9 11.5": ["ujima"], "-0.4 5.5 0.6": ["sakazakii"], "9.2 11.9 21.3": ["shortgrass"], "6.1 11.5 24.0": ["hackey"], "-0.7 0.2 9.0": ["mahfil"], "-1.2 8.6 14.7": ["turun"], "7.5 7.9 6.8": ["plonky"], "-13.5 5.9 -1.2": ["unfav"], "-2.4 4.0 6.8": ["causus"], "3.9 10.6 7.9": ["antihelium"], "8.5 8.4 18.6": ["somniferum"], "2.2 7.1 20.7": ["faba"], "0.3 18.3 12.2": ["uttar"], "3.2 13.9 2.9": ["mucociliary"], "9.8 13.7 23.4": ["casebearer"], "12.5 5.3 -7.2": ["tetryl"], "2.1 4.3 2.7": ["acyltransferase"], "11.1 7.1 8.6": ["centrics"], "-9.0 11.5 4.3": ["unacted"], "2.8 13.0 2.9": ["borreliosis"], "-2.8 10.1 7.1": ["regon"], "3.3 12.7 14.9": ["lobortis"], "-2.4 2.3 10.0": ["nonresponding"], "5.5 -2.2 7.9": ["zow"], "8.3 -3.5 11.4": ["curred"], "3.1 13.8 10.6": ["carbonize"], "11.2 8.0 24.8": ["foetidus"], "0.0 1.4 -4.2": ["barackobama"], "15.9 5.0 15.2": ["torsoed"], "1.8 3.0 8.5": ["sve"], "0.7 15.0 24.0": ["parasiticus"], "16.3 -0.9 7.6": ["mahindra"], "10.4 6.5 7.4": ["glassfiber"], "8.9 14.0 7.8": ["nautch"], "7.7 5.0 15.5": ["violette"], "8.0 5.1 28.8": ["quinquefasciatus"], "9.5 14.5 17.5": ["bluetick"], "7.8 13.2 -1.5": ["forspeed"], "-6.3 5.1 13.2": ["trinucleotide"], "7.0 -9.5 -2.4": ["ceuticals"], "9.6 15.4 11.9": ["mained"], "7.3 6.8 20.3": ["tarda"], "16.6 7.3 9.3": ["publicidad"], "1.3 17.8 8.8": ["mothaf"], "7.5 -4.5 12.0": ["rde"], "24.5 8.1 16.0": ["roached"], "17.6 -6.5 5.8": ["mercials"], "14.6 -3.8 21.9": ["girolle"], "5.2 9.1 13.1": ["chahta"], "18.3 19.0 8.7": ["aurum"], "6.1 2.9 4.6": ["advant"], "0.1 16.5 4.5": ["disharmonic"], "-3.3 -8.7 -2.7": ["rease"], "-1.8 1.3 19.6": ["usapin"], "4.2 4.8 24.1": ["moco"], "-0.3 1.9 1.6": ["cullin"], "5.1 15.4 11.6": ["revolters"], "0.1 15.3 14.4": ["gravidarum"], "1.2 1.6 12.8": ["uprima"], "21.0 13.5 12.7": ["wanging"], "22.2 7.2 10.2": ["convectors"], "4.5 4.6 10.7": ["ileocecal"], "12.2 8.7 10.3": ["characer"], "11.0 14.1 42.7": ["deveining"], "9.9 6.5 8.2": ["schwarzenegger"], "-5.2 5.0 6.6": ["centistokes"], "-1.1 3.4 5.3": ["dheere"], "12.5 3.8 19.7": ["polies"], "1.7 13.9 7.5": ["esteban"], "9.6 1.5 9.6": ["adirondack"], "13.1 1.4 40.3": ["akoya"], "3.1 -0.3 12.1": ["dupers"], "8.4 11.7 12.1": ["herf"], "4.2 0.2 8.4": ["pamoate"], "6.4 0.6 1.8": ["nanobioscience"], "9.9 17.1 7.1": ["wamp"], "20.5 -6.3 -3.6": ["centralpark"], "16.5 12.3 23.3": ["tlee"], "-15.6 -1.7 -3.0": ["crossclamp"], "-3.9 7.6 5.4": ["methylergonovine"], "-3.6 1.5 1.6": ["anagrelide"], "16.7 2.0 4.9": ["rollered"], "2.0 1.4 33.8": ["buerre"], "16.2 15.4 20.7": ["pakul"], "19.1 5.7 9.1": ["funtwo"], "2.8 9.6 14.8": ["chloasma"], "-1.1 8.3 6.6": ["synthetases"], "2.9 3.6 5.4": ["ricetta"], "1.8 10.4 -0.4": ["aretz"], "9.3 -11.7 3.5": ["appar"], "8.1 1.2 4.5": ["tsb"], "8.7 14.2 9.0": ["schwer"], "13.4 -1.1 1.0": ["shopcraft"], "2.9 22.8 12.2": ["saccadic"], "4.9 3.9 15.9": ["consecrators"], "-0.8 6.5 18.9": ["humingi"], "6.3 -2.0 16.9": ["absinthium"], "10.4 13.4 13.0": ["knotch"], "-0.7 9.0 5.1": ["consecrator"], "8.4 4.7 7.4": ["doigts"], "13.5 5.0 35.9": ["cochinita"], "16.7 13.9 33.3": ["danio"], "11.3 2.5 13.2": ["paiement"], "10.0 -3.7 12.0": ["nephrostomy"], "2.7 4.5 10.0": ["plasmacytoid"], "-1.4 2.4 9.0": ["cessful"], "7.7 7.3 10.6": ["fluidizer"], "3.3 -3.1 6.2": ["atheromatous"], "-2.9 10.5 15.9": ["binibigay"], "8.4 -2.4 12.9": ["hoja"], "7.6 10.4 8.0": ["novus"], "3.4 10.9 11.7": ["pneumocytes"], "9.9 14.7 5.4": ["unaccreted"], "1.8 -3.6 3.1": ["tss"], "-1.6 -5.4 4.0": ["poursuit"], "5.3 -0.2 26.0": ["jerkey"], "7.3 4.0 6.5": ["environmentaly"], "10.5 10.8 12.0": ["widro"], "10.8 13.6 11.8": ["tremblings"], "-6.0 4.9 5.4": ["neuroregenerative"], "3.0 -2.5 8.7": ["jected"], "5.0 17.9 16.4": ["garibi"], "-4.1 -5.5 1.6": ["clav"], "7.5 11.3 10.6": ["multidepartment"], "4.2 18.8 18.6": ["fomc"], "-0.8 -5.5 7.1": ["restruc"], "16.2 16.6 14.1": ["lunchmates"], "8.7 5.3 11.1": ["husted"], "9.4 -0.4 8.9": ["museumday"], "1.1 23.7 -2.0": ["judeo"], "7.3 6.4 9.6": ["estim"], "6.9 -3.8 2.4": ["hydroconversion"], "1.3 -1.9 11.7": ["pite"], "4.9 8.1 4.6": ["ionotropic"], "15.3 9.0 11.5": ["saucerlike"], "-8.4 -12.2 3.5": ["restric"], "-0.9 5.1 3.3": ["emis"], "6.3 10.2 5.8": ["telepark"], "-1.1 0.8 4.3": ["delphia"], "12.8 21.2 18.3": ["perfringens"], "7.4 10.2 18.9": ["milta"], "2.0 5.0 13.6": ["kitu"], "0.6 -2.4 2.2": ["hyperbranched"], "-1.7 5.5 6.4": ["kyum"], "10.0 18.9 11.4": ["cytometric"], "10.9 -1.1 19.0": ["partylike"], "-4.6 2.9 4.6": ["fluocinonide"], "21.6 8.6 23.3": ["bunya"], "4.8 2.2 2.6": ["vmdk"], "11.7 6.2 2.4": ["awide"], "-2.8 4.7 2.8": ["esophagogastric"], "10.9 11.2 31.2": ["bettong"], "8.7 8.6 4.7": ["jimmyfallon"], "7.2 8.7 15.7": ["poter"], "28.6 14.6 32.8": ["snowlike"], "8.0 17.1 12.0": ["robh"], "-5.6 3.3 3.8": ["dyskinetic"], "3.2 11.7 10.5": ["thern"], "2.0 -7.0 -0.2": ["carboxylase"], "-3.7 11.9 11.6": ["grees"], "-3.5 -15.0 -8.9": ["craigshipp"], "12.6 21.2 7.2": ["backpackable"], "10.8 13.3 2.5": ["uriminzokkiri"], "1.3 -8.9 0.9": ["clinico"], "-3.1 10.3 16.4": ["tranh"], "16.0 12.9 20.5": ["keenan"], "3.9 -3.5 12.6": ["bitartrate"], "-1.8 15.0 10.5": ["pacem"], "-0.7 -4.6 1.3": ["ghars"], "8.0 3.9 8.0": ["avvocato"], "10.2 10.7 4.8": ["ringxiety"], "18.0 14.9 30.5": ["huhu"], "3.8 3.4 8.2": ["aktres"], "7.1 14.8 18.1": ["rahein"], "-2.2 5.1 4.5": ["enforecement"], "5.5 -0.1 9.0": ["rythu"], "2.5 11.7 14.8": ["springdaleark"], "15.8 12.7 16.3": ["floresiensis"], "8.4 15.7 9.9": ["memari"], "10.3 -3.6 13.7": ["eesa"], "1.0 8.9 13.6": ["wtd"], "5.1 13.8 9.6": ["thermostatically"], "14.6 9.9 9.1": ["greenspan"], "6.7 15.0 1.8": ["courtcraft"], "3.8 14.7 10.7": ["peregruzka"], "3.6 4.8 -8.3": ["orial"], "5.6 16.1 11.6": ["critcally"], "-3.7 12.8 9.8": ["tempora"], "-1.1 -2.1 -1.3": ["outil"], "4.3 7.2 4.0": ["tenascin"], "10.2 8.1 18.1": ["rockchip"], "-5.9 3.7 7.1": ["exercis"], "2.9 0.2 4.3": ["nonrevolving"], "11.8 3.0 13.0": ["permettra"], "-3.9 -0.0 1.1": ["mpt"], "10.8 -4.6 1.9": ["velocimetry"], "5.1 6.5 10.3": ["carling"], "11.1 15.2 19.5": ["alatus"], "5.2 10.9 3.4": ["unsales"], "-0.7 11.5 14.0": ["tekst"], "10.1 -14.8 3.0": ["kohr"], "6.4 -4.0 3.0": ["incontro"], "11.9 4.3 23.1": ["cohosh"], "6.6 6.0 12.7": ["envie"], "0.7 12.0 5.3": ["ucts"], "6.8 9.3 6.9": ["reddot"], "5.9 11.9 14.5": ["choh"], "0.6 12.4 11.3": ["supermoons"], "15.4 3.7 3.0": ["wickless"], "2.6 1.4 -0.4": ["haemophilus"], "0.4 0.9 -2.5": ["breakingnews"], "-0.4 -0.3 9.3": ["mrk"], "-6.3 1.8 9.5": ["hydrochlorofluorocarbon"], "1.9 6.1 22.3": ["takbo"], "11.9 19.5 12.2": ["christs"], "13.5 22.0 4.8": ["remotecontrolled"], "10.4 9.4 11.0": ["cloacae"], "6.0 10.8 13.5": ["ochocinco"], "0.9 12.8 7.1": ["ascriptions"], "14.1 12.1 10.0": ["wrigley"], "2.5 4.1 14.3": ["sylvatica"], "5.7 11.2 11.2": ["baritic"], "13.8 3.3 9.1": ["poppingly"], "6.7 19.0 4.8": ["rasist"], "8.5 5.6 26.0": ["bawk"], "1.2 5.0 4.4": ["benzothiazole"], "16.6 4.3 33.6": ["kokopu"], "1.9 24.2 -4.9": ["blackops"], "6.1 6.4 8.7": ["kamera"], "6.5 -0.1 10.0": ["disgwyl"], "1.9 -3.5 9.7": ["amenitized"], "7.9 15.0 25.5": ["bisi"], "13.7 0.3 29.2": ["toscano"], "15.3 3.8 3.9": ["twiddler"], "2.2 2.5 2.7": ["publier"], "3.1 11.0 12.3": ["cradlesong"], "-6.5 15.6 -6.0": ["encour"], "16.3 5.4 22.8": ["landis"], "-1.0 3.3 9.6": ["falutin"], "16.9 1.2 30.4": ["fritta"], "10.9 10.1 2.1": ["bizrate"], "-3.4 7.4 -1.5": ["expressors"], "5.3 11.7 12.4": ["stoppingly"], "1.6 2.2 15.3": ["tungkol"], "8.5 5.4 11.5": ["microtiter"], "5.1 4.2 8.2": ["mantic"], "8.0 16.5 10.9": ["dilatant"], "8.1 12.2 10.1": ["bellyhold"], "-5.5 8.4 4.2": ["inconvertibility"], "11.4 18.5 20.3": ["knapper"], "5.1 12.8 18.8": ["paralyzer"], "20.1 3.7 37.7": ["fundido"], "9.8 0.6 0.0": ["readacross"], "4.3 12.5 10.6": ["jaate"], "7.7 -4.0 -1.2": ["qualifieds"], "8.2 -0.0 -1.5": ["musculo"], "-0.1 -0.0 3.5": ["carboxylic"], "8.0 -2.8 -0.5": ["tuhr"], "8.0 1.5 5.9": ["bicomponent"], "-0.6 -6.2 1.9": ["embauche"], "6.9 -3.6 14.8": ["intertrack"], "2.7 7.7 3.2": ["vaibhav"], "4.1 10.8 16.0": ["fenton"], "2.6 6.0 4.6": ["henever"], "7.7 11.9 3.9": ["songy"], "8.6 3.3 13.2": ["palmitic"], "-2.1 3.4 3.3": ["independ"], "9.6 -4.6 10.9": ["picolinate"], "14.7 9.9 29.3": ["carcharias"], "12.3 12.5 14.1": ["protopunk"], "16.7 17.3 24.6": ["twizzler"], "11.4 2.4 13.8": ["dimethylformamide"], "-9.6 -5.6 3.6": ["substan"], "2.8 5.0 10.6": ["usf"], "2.9 11.9 1.2": ["lipoglycopeptide"], "-6.7 -6.2 7.7": ["keting"], "-1.4 6.4 11.7": ["nando"], "-7.5 1.8 5.2": ["osteochondritis"], "-4.1 3.1 -1.9": ["expresse"], "6.6 5.4 15.1": ["drusy"], "9.3 -5.1 1.8": ["portation"], "7.5 8.6 11.8": ["kubo"], "8.9 5.2 32.0": ["caretta"], "3.4 6.8 8.9": ["inflammatories"], "-1.6 -1.9 9.8": ["iec"], "7.4 10.4 14.9": ["yotch"], "15.1 8.4 15.5": ["supervalue"], "-2.1 1.7 11.6": ["attri"], "4.0 10.5 10.7": ["dlh"], "12.7 -0.0 14.2": ["panchaloha"], "10.6 8.8 14.6": ["ozpa"], "6.8 -1.6 23.8": ["wirehaired"], "15.7 28.3 3.6": ["darth"], "12.8 9.0 18.7": ["aweigh"], "12.0 6.1 13.3": ["dovey"], "11.2 4.9 23.5": ["hobie"], "10.0 7.6 5.9": ["unmineable"], "-7.9 -7.0 -5.3": ["ipse"], "4.1 11.7 4.0": ["voic"], "9.7 2.2 5.3": ["stannous"], "-2.3 5.4 3.9": ["nonadopted"], "5.2 12.6 8.8": ["nonembryonic"], "10.3 16.7 22.5": ["spinks"], "15.8 9.5 15.6": ["reces"], "7.4 13.4 17.6": ["gelsolin"], "6.1 10.0 16.2": ["ooga"], "22.0 8.1 31.6": ["gummie"], "11.4 36.0 7.0": ["nuclearizing"], "-3.6 7.2 7.6": ["supracrustal"], "11.1 10.4 3.4": ["xulrunner"], "2.0 -4.0 9.1": ["unicondylar"], "-3.6 0.1 -4.1": ["metin"], "6.7 5.7 9.3": ["underpredicted"], "-0.4 -0.1 2.0": ["sra"], "1.3 6.5 9.8": ["swarthier"], "0.5 3.9 14.1": ["argu"], "2.9 8.4 18.7": ["parahaemolyticus"], "8.7 2.8 16.2": ["divina"], "8.6 11.4 5.4": ["empted"], "6.6 0.1 7.2": ["oween"], "3.9 12.9 15.7": ["peinture"], "2.5 14.2 14.1": ["terabecquerel"], "-5.4 5.5 3.6": ["acuities"], "1.7 4.4 18.0": ["monosaturated"], "-0.6 5.0 3.2": ["toupdate"], "-5.5 -13.5 -7.4": ["apcustomersupport"], "8.6 3.3 18.4": ["capacidad"], "25.1 5.9 20.4": ["newel"], "-3.2 6.8 6.5": ["bachat"], "7.3 0.9 1.8": ["aquila"], "4.2 8.8 15.0": ["tauhan"], "6.5 -1.6 4.3": ["shopathon"], "6.7 -6.7 13.6": ["scription"], "1.0 7.1 11.7": ["foodism"], "-2.6 16.9 15.4": ["pkl"], "2.0 11.6 2.5": ["cyclingnews"], "4.5 9.7 9.6": ["sangharsh"], "11.4 -3.0 10.4": ["multiwalled"], "11.9 7.0 29.8": ["parula"], "10.4 -1.6 8.6": ["raschel"], "-3.7 -2.1 -1.1": ["samities"], "-15.6 0.0 0.8": ["metacarpophalangeal"], "10.2 1.4 19.9": ["oaten"], "3.6 7.7 28.0": ["suzette"], "10.9 6.5 16.0": ["traje"], "20.9 7.6 -2.5": ["jetbridges"], "6.4 1.8 7.7": ["allem"], "10.2 7.3 16.5": ["revoir"], "1.6 -1.2 -4.9": ["institu"], "6.9 -0.8 18.0": ["gueule"], "10.5 0.1 16.4": ["peared"], "15.2 10.2 10.8": ["paraphrenalia"], "1.5 4.6 4.3": ["kamiz"], "-1.0 1.2 7.3": ["vici"], "15.7 8.0 22.1": ["hindcasting"], "5.1 6.0 4.9": ["brivanib"], "6.6 31.1 9.8": ["knowthe"], "9.2 7.8 15.3": ["kehte"], "2.6 6.9 13.5": ["lery"], "-2.6 6.3 1.7": ["renally"], "6.2 -2.4 0.3": ["settore"], "10.3 16.2 16.7": ["ordinates"], "6.7 11.1 15.9": ["humani"], "7.8 2.2 13.9": ["pand"], "3.5 9.5 1.4": ["dramatis"], "12.6 0.7 4.4": ["penlike"], "7.0 26.6 13.2": ["knowest"], "2.1 8.3 9.2": ["appels"], "12.8 2.4 14.3": ["puertas"], "5.2 8.8 -2.3": ["ivoire"], "7.9 -3.3 -4.3": ["bcr"], "3.0 -10.5 -4.1": ["ecutive"], "12.9 17.2 17.4": ["misere"], "-1.1 3.4 7.0": ["vobis"], "7.0 8.4 -1.7": ["technica"], "-3.2 5.5 13.7": ["intracytoplasmic"], "-4.6 2.1 8.7": ["schizophreniform"], "17.9 4.9 16.1": ["geiger"], "4.0 -6.2 5.5": ["cruces"], "5.4 -0.2 12.8": ["middlewoman"], "7.1 -4.8 3.4": ["acquistare"], "21.9 8.4 17.5": ["oyamel"], "9.0 13.8 24.4": ["dipterocarp"], "-0.4 8.9 15.5": ["doku"], "-4.0 6.1 1.8": ["recogni"], "8.2 18.2 12.6": ["saunalike"], "12.9 5.8 2.5": ["leged"], "-4.3 0.0 5.6": ["mabigyan"], "9.9 8.1 17.8": ["thaliana"], "7.8 -1.0 3.6": ["onrec"], "7.9 4.1 15.9": ["hachi"], "16.0 -0.8 45.1": ["littleneck"], "11.0 -4.7 24.3": ["mandel"], "1.6 10.4 8.3": ["maloom"], "1.7 -0.4 5.5": ["valerate"], "22.3 11.0 24.1": ["andwhite"], "-9.0 1.2 2.9": ["kyi"], "7.2 13.9 8.3": ["drinkypoo"], "3.5 1.5 9.3": ["presolicitation"], "6.8 -0.6 5.7": ["swatching"], "4.9 6.4 4.7": ["sonoro"], "14.4 6.8 13.0": ["pillowfight"], "-6.7 4.1 5.2": ["recevoir"], "2.4 4.6 7.7": ["hepatoprotective"], "-4.3 1.6 -1.3": ["tihn"], "2.4 4.2 17.7": ["formic"], "8.1 15.6 3.4": ["indignados"], "1.6 1.4 0.5": ["essing"], "4.6 9.2 8.7": ["malos"], "4.6 -5.7 2.7": ["helpu"], "16.5 8.5 14.8": ["tannest"], "6.4 7.8 9.0": ["biens"], "9.8 -5.1 5.1": ["tertainment"], "1.2 -6.7 9.2": ["voicetracking"], "-8.8 0.1 2.2": ["availa"], "-0.5 -7.2 3.7": ["accommo"], "6.7 7.8 12.4": ["pentrite"], "22.5 14.9 21.0": ["sssss"], "12.4 10.1 17.0": ["dupioni"], "0.0 -0.1 -1.3": ["bertahlil"], "4.4 0.1 3.1": ["hhc"], "-4.5 5.9 11.6": ["veni"], "4.3 6.8 37.5": ["darkhouse"], "-1.9 -0.9 19.0": ["tify"], "15.3 7.6 5.6": ["orbitz"], "12.5 10.8 -1.6": ["tratar"], "0.3 0.5 7.6": ["nold"], "-3.2 -1.4 -1.0": ["retary"], "4.0 21.6 15.6": ["whigs"], "0.2 8.6 12.6": ["ekor"], "17.2 3.8 14.5": ["capra"], "5.7 9.7 11.9": ["siento"], "15.7 20.2 19.2": ["sallying"], "23.9 9.3 29.2": ["boab"], "-2.7 1.2 13.5": ["liams"], "0.2 11.3 -1.9": ["quos"], "8.1 33.0 7.9": ["qassam"], "8.2 7.4 13.8": ["humanus"], "-4.3 -0.2 11.5": ["mnr"], "0.6 7.0 5.2": ["witts"], "10.6 8.8 19.2": ["booga"], "16.7 8.2 13.6": ["greencelebrity"], "5.2 3.0 13.8": ["thermophilus"], "8.4 -2.5 5.8": ["rmation"], "10.3 18.5 10.3": ["downable"], "-8.6 -8.6 -2.7": ["toring"], "16.2 5.1 14.7": ["pira"], "9.7 5.7 10.2": ["passen"], "18.2 6.0 18.8": ["palomas"], "9.2 18.2 13.1": ["bhut"], "7.3 12.2 17.3": ["ingestive"], "-1.7 -6.1 10.8": ["lding"], "11.9 14.2 14.3": ["fluorimetry"], "16.5 6.5 10.9": ["dinitrotoluene"], "6.3 4.2 0.7": ["lynnsweet"], "-6.4 6.6 16.3": ["biao"], "2.5 4.2 1.7": ["heartaching"], "10.3 -3.8 4.6": ["prefillable"], "12.3 6.5 8.1": ["kidogo"], "13.4 10.4 12.7": ["hotsy"], "1.2 -11.7 -0.9": ["skoh"], "12.4 -3.3 28.3": ["glaces"], "6.6 5.3 9.5": ["anganwari"], "1.1 6.8 9.2": ["somatoform"], "-0.3 7.1 6.9": ["clusive"], "-3.9 2.4 -5.1": ["securityholding"], "-0.8 11.0 2.2": ["faecalis"], "-4.0 6.1 2.9": ["cnnbrk"], "3.6 10.7 17.6": ["fowleri"], "0.7 3.5 4.5": ["hyoscyamine"], "7.5 7.7 5.3": ["spikings"], "3.7 8.0 10.8": ["statementsare"], "2.0 0.7 7.2": ["logement"], "13.9 7.4 15.5": ["catorce"], "14.6 6.4 13.0": ["counterboring"], "0.9 13.3 -2.2": ["vivos"], "-3.3 6.6 1.8": ["papillomatosis"], "25.5 6.3 20.6": ["midcalorie"], "0.0 16.5 16.6": ["eratically"], "7.4 19.5 16.8": ["verybody"], "8.7 5.8 8.8": ["myelodysplastic"], "7.1 -7.0 14.2": ["refin"], "0.3 6.3 12.3": ["intels"], "11.0 12.3 16.3": ["peened"], "15.1 -4.3 -10.1": ["ebm"], "-3.3 3.4 3.4": ["esday"], "5.1 2.5 4.5": ["furnaceware"], "-4.7 -3.5 -0.8": ["suspen"], "-10.1 1.8 5.3": ["inngoers"], "0.4 4.4 10.5": ["bombi"], "-0.4 6.7 13.7": ["biu"], "11.4 24.4 15.2": ["preponderates"], "12.2 -1.2 12.8": ["tourisme"], "-0.2 6.7 3.1": ["retinyl"], "6.3 11.0 5.9": ["wwww"], "0.5 -2.3 4.4": ["scolaires"], "-3.4 6.6 0.4": ["describ"], "11.0 22.9 21.0": ["wayworn"], "10.0 8.3 11.1": ["amani"], "9.5 2.1 26.1": ["blackeyed"], "-0.5 7.8 2.4": ["nonvaccine"], "13.1 8.8 18.1": ["denitrifying"], "-4.4 2.6 12.2": ["tungod"], "-1.8 12.3 8.0": ["tection"], "2.5 13.9 11.9": ["besteht"], "3.0 7.8 9.8": ["tamanna"], "-2.5 8.4 18.5": ["nagsasabi"], "7.4 9.6 5.6": ["haseena"], "-0.8 22.1 5.2": ["semitism"], "8.7 -2.1 12.3": ["blynedd"], "20.1 18.6 10.0": ["dichlorodiphenyltrichloroethane"], "3.7 8.8 11.3": ["sueno"], "-1.4 -6.7 6.3": ["econazole"], "-1.1 7.2 13.6": ["korbo"], "18.9 8.2 33.6": ["swordtail"], "3.1 8.4 13.9": ["iisip"], "5.4 -0.7 6.7": ["offrir"], "6.1 6.6 16.4": ["campeonato"], "10.2 -0.9 4.1": ["mariolavandeira"], "4.4 6.2 12.1": ["latha"], "10.3 7.4 8.3": ["kujichagulia"], "-0.2 13.0 7.6": ["indem"], "5.8 9.0 28.2": ["gallina"], "8.4 13.9 30.3": ["akepa"], "-2.0 16.9 7.2": ["chevra"], "1.3 19.7 9.2": ["trainging"], "22.3 14.3 24.2": ["vieille"], "10.1 18.4 5.8": ["bustingly"], "6.6 1.4 -4.7": ["maytansinoid"], "8.3 10.3 12.0": ["throwings"], "-1.5 -6.7 9.6": ["debuginfo"], "6.6 10.9 14.3": ["jdd"], "12.9 7.9 14.9": ["nosibalasi"], "9.4 11.4 12.8": ["ptomaine"], "1.5 9.6 13.6": ["gaston"], "10.2 21.6 15.6": ["wackadoos"], "-1.5 -7.6 -4.3": ["intravitreous"], "5.5 8.4 4.1": ["easyday"], "-0.2 15.9 14.0": ["sponsible"], "6.0 3.5 17.1": ["obtenir"], "12.3 8.6 6.8": ["fessional"], "17.2 2.7 27.8": ["gribiche"], "-8.1 7.4 3.8": ["boyer"], "17.8 -1.8 8.0": ["undercabinet"], "7.3 -4.5 10.9": ["produire"], "-1.0 -1.4 -3.4": ["rburgring"], "-5.4 8.9 -0.8": ["pentothal"], "11.4 27.8 13.7": ["dragout"], "3.0 2.7 2.7": ["hausse"], "7.8 -2.2 10.0": ["titanum"], "1.3 13.4 8.3": ["speakup"], "9.4 6.9 40.6": ["cownose"], "-5.4 2.4 12.8": ["chaku"], "12.8 26.8 0.4": ["frontierland"], "5.5 0.1 4.6": ["mucoregulator"], "2.5 3.5 18.8": ["bacillary"], "3.4 8.0 7.5": ["gewinnen"], "15.7 11.1 7.2": ["ringy"], "10.9 -0.0 0.9": ["dicted"], "-2.6 7.5 1.6": ["nejad"], "10.8 10.8 -5.8": ["energo"], "4.9 -2.8 15.9": ["greggii"], "6.7 8.3 21.0": ["particu"], "7.6 -0.3 12.9": ["umchwasho"], "2.8 6.4 18.9": ["ultraconserved"], "22.2 12.7 22.0": ["grapelike"], "2.8 6.4 18.2": ["sanay"], "5.6 1.3 3.3": ["mehd"], "11.2 6.2 6.9": ["verden"], "4.4 1.8 10.5": ["nahr"], "12.9 12.1 27.5": ["baldachin"], "4.8 15.8 -0.7": ["neotraditionalist"], "4.7 -1.1 13.6": ["gwyn"], "15.0 2.0 24.4": ["aestivum"], "11.2 6.3 18.4": ["baird"], "17.2 -0.2 10.6": ["munications"], "15.3 4.9 19.4": ["briquetted"], "3.3 10.8 7.8": ["cultur"], "16.3 6.8 29.7": ["layings"], "7.8 3.2 0.6": ["republika"], "-7.5 17.3 -1.2": ["interpositions"], "7.6 8.9 17.9": ["bodie"], "8.1 23.3 5.2": ["revilers"], "-5.2 7.9 1.0": ["anw"], "17.7 12.3 13.1": ["nanohole"], "-3.3 11.4 6.1": ["sanguinis"], "7.1 -2.6 12.7": ["fartsy"], "3.9 12.6 16.6": ["negotiables"], "6.4 15.8 2.4": ["overrided"], "2.1 -7.9 8.1": ["rbd"], "6.7 5.4 -3.4": ["airwide"], "-2.9 1.6 16.6": ["pyrantel"], "3.8 -5.9 11.0": ["rulesmaking"], "-1.5 1.8 -0.1": ["laine"], "15.5 20.2 14.1": ["onsumers"], "-0.7 -1.4 10.2": ["tity"], "10.7 22.9 16.2": ["drywood"], "8.5 -7.2 21.4": ["hulless"], "4.8 4.3 14.0": ["cryptoxanthin"], "6.6 11.5 13.1": ["yk"], "0.2 1.1 6.5": ["hautes"], "-3.6 -10.1 2.1": ["hsg"], "11.0 -6.7 3.0": ["ceutical"], "3.9 17.7 4.2": ["ffxi"], "-1.8 21.1 5.3": ["nonpeaceful"], "1.0 16.3 12.8": ["basanti"], "8.5 4.2 17.6": ["geisio"], "11.1 5.3 9.2": ["argentiferous"], "9.2 6.1 15.6": ["tiyak"], "11.5 2.6 13.4": ["cifras"], "7.4 12.3 16.9": ["sosa"], "12.5 -6.6 0.3": ["minidisks"], "12.1 2.4 13.4": ["geomicrobiology"], "12.0 12.7 13.1": ["dolorosa"], "11.4 4.9 18.5": ["transporte"], "7.7 3.0 17.3": ["bodas"], "11.6 0.9 13.2": ["bellsouth"], "-9.6 4.7 3.5": ["nonmyeloablative"], "26.1 0.8 4.8": ["klieg"], "2.1 16.7 11.4": ["devasated"], "-0.4 4.4 9.7": ["knobbing"], "-2.4 9.6 -0.9": ["ofseven"], "3.8 -8.1 4.8": ["ntp"], "-5.4 7.1 0.2": ["statementscontained"], "6.1 -1.8 14.0": ["immi"], "13.7 7.3 14.1": ["marram"], "9.6 8.5 27.1": ["greenwing"], "14.7 5.3 24.8": ["mamane"], "7.0 -0.1 12.9": ["camisa"], "7.9 10.1 12.0": ["wanto"], "12.8 15.7 7.3": ["inertially"], "1.0 3.5 12.2": ["zid"], "9.9 -1.9 24.6": ["sabal"], "6.1 5.9 -7.7": ["emiri"], "9.8 20.6 0.8": ["comandos"], "5.9 -12.6 14.7": ["acadienne"], "10.5 6.5 12.8": ["gule"], "12.6 8.2 21.5": ["loungelike"], "0.7 -1.1 -2.8": ["communica"], "3.3 17.3 18.7": ["greer"], "6.4 6.7 4.9": ["griffiths"], "2.1 -2.5 9.1": ["enseignement"], "2.0 3.4 8.9": ["diffi"], "9.6 19.6 18.1": ["knockaround"], "14.5 0.0 17.1": ["papiers"], "5.9 9.1 0.4": ["zations"], "-1.2 10.6 15.3": ["typhi"], "4.6 3.4 0.0": ["obstante"], "2.7 14.0 -8.4": ["fortu"], "5.8 6.4 6.7": ["electrotherapeutic"], "28.3 5.5 19.8": ["carbonfiber"], "9.3 4.9 10.7": ["hollyrpeete"], "-0.3 16.0 6.4": ["mediately"], "14.5 -1.0 8.7": ["euronext"], "9.7 4.6 1.6": ["uriminzok"], "17.9 -6.7 -2.5": ["adenin"], "-2.1 1.6 9.7": ["neuritic"], "-1.9 23.1 8.9": ["repudiatory"], "10.7 -0.5 7.7": ["thalasso"], "5.7 12.9 3.0": ["sulting"], "2.7 1.4 1.0": ["nepa"], "10.6 14.0 7.3": ["shutterless"], "2.5 -5.8 6.3": ["gehn"], "7.0 5.4 11.9": ["pelite"], "11.0 7.3 6.8": ["newinformation"], "15.5 23.7 4.2": ["ablazing"], "1.6 17.3 13.2": ["redistributional"], "14.4 9.3 17.1": ["clary"], "15.9 -6.8 3.2": ["infopath"], "-5.8 2.3 -2.5": ["neuropsych"], "7.9 1.7 7.3": ["unofficiated"], "10.5 8.6 16.1": ["kamon"], "-5.7 1.4 -0.1": ["meisten"], "-0.5 3.7 -0.8": ["curity"], "18.4 2.7 21.0": ["stemmer"], "8.4 10.2 7.3": ["cupric"], "10.1 5.9 11.9": ["segmentable"], "-2.3 5.5 14.2": ["cently"], "13.1 -3.4 7.3": ["volledige"], "6.2 2.9 7.9": ["amonafide"], "-4.7 4.1 -7.6": ["somo"], "2.8 19.0 6.3": ["unshirkable"], "-7.3 -1.4 2.8": ["guhs"], "20.9 4.8 2.5": ["nomy"], "5.1 -0.5 9.8": ["identidad"], "4.4 3.6 21.8": ["cyanogenic"], "8.9 9.5 11.5": ["immedi"], "7.5 -3.5 5.4": ["calcul"], "-6.3 5.4 5.9": ["neers"], "10.7 16.2 11.5": ["soulja"], "4.6 8.2 7.1": ["tetrahydragestrinone"], "1.7 -0.7 7.0": ["hydroxylapatite"], "-3.0 7.7 3.7": ["sults"], "17.4 21.0 13.7": ["corpuscular"], "10.9 8.8 17.2": ["percy"], "2.0 7.3 10.7": ["ersonal"], "7.9 4.9 14.1": ["maen"], "9.3 9.8 12.0": ["incide"], "7.1 23.2 11.9": ["semite"], "17.1 6.1 8.6": ["unheading"], "-3.7 -0.4 13.2": ["dorsalis"], "15.4 14.6 21.3": ["flams"], "4.8 4.8 10.1": ["cesarian"], "7.0 10.5 20.1": ["makakuha"], "3.2 4.3 3.9": ["lactoglobulin"], "6.3 -0.1 10.0": ["participar"], "11.1 10.8 12.8": ["maaro"], "24.3 10.1 15.9": ["disposible"], "8.8 11.6 22.4": ["briquet"], "15.4 15.5 13.4": ["nellies"], "4.1 1.8 2.3": ["exelon"], "23.3 10.8 4.3": ["lockmaker"], "14.7 2.8 24.7": ["roca"], "-0.2 4.3 12.4": ["naisip"], "5.3 14.2 2.6": ["draged"], "10.1 14.6 42.0": ["waterfleas"], "-4.5 4.6 10.1": ["enf"], "2.0 12.4 7.9": ["cytopathic"], "1.3 11.2 8.7": ["weighins"], "6.9 8.7 9.3": ["prestressing"], "6.6 4.6 23.1": ["pavs"], "11.2 3.6 20.7": ["silla"], "12.7 13.6 19.7": ["kermode"], "4.2 3.2 1.9": ["kwasa"], "0.5 3.3 4.9": ["afflux"], "5.4 19.1 24.1": ["blinde"], "-6.1 6.2 10.5": ["hypervolemic"], "9.0 11.1 25.3": ["diawl"], "6.3 2.5 17.7": ["leit"], "-8.5 -5.3 -0.6": ["itpr"], "11.5 21.2 16.3": ["uppies"], "9.4 8.9 11.0": ["freefile"], "13.0 14.2 14.1": ["coresuite"], "-0.1 1.3 2.7": ["granulocytic"], "17.8 3.7 33.2": ["saltado"], "4.4 2.0 0.1": ["nlike"], "9.1 6.9 21.9": ["monsieurs"], "-4.3 1.5 6.2": ["esthesioneuroblastoma"], "16.8 4.7 18.8": ["demonium"], "13.9 13.7 17.9": ["hemopexin"], "15.5 7.9 15.4": ["royce"], "2.4 12.1 13.7": ["malabo"], "8.0 4.5 5.2": ["meilleures"], "0.1 9.0 5.5": ["ketolide"], "2.7 -1.1 0.8": ["omnicef"], "4.8 6.9 5.3": ["yil"], "-2.9 -6.4 -3.1": ["phenylacetate"], "-1.3 26.2 9.3": ["presurge"], "10.0 2.3 8.0": ["atteindre"], "5.5 11.2 18.6": ["polydactylism"], "-5.5 4.7 15.4": ["cspan"], "5.0 10.1 5.1": ["retentiveness"], "8.4 -1.3 10.5": ["shmancy"], "17.2 5.5 15.6": ["mcintoshi"], "14.9 5.7 12.7": ["chugga"], "3.3 12.9 7.5": ["intill"], "15.9 3.0 24.0": ["maritimus"], "4.4 1.6 3.7": ["enregistrer"], "4.6 19.4 12.8": ["onbase"], "16.8 8.2 9.6": ["megacryometeor"], "12.8 6.4 6.0": ["taler"], "1.1 13.9 6.5": ["hahm"], "-0.7 6.2 -1.0": ["pedic"], "20.7 3.9 17.4": ["mopani"], "2.2 4.2 -5.4": ["incopy"], "-11.9 -7.5 3.7": ["iel"], "0.7 5.2 -0.6": ["nonautomatic"], "-2.6 4.4 10.7": ["pretelecast"], "3.1 9.4 8.1": ["eqv"], "1.4 16.2 5.4": ["unscouted"], "9.6 -2.6 6.9": ["gestione"], "10.7 9.2 9.4": ["pectations"], "2.2 1.7 1.3": ["photocasts"], "-0.8 11.6 11.2": ["fortable"], "8.6 16.3 1.7": ["untagging"], "3.3 10.2 6.5": ["easygates"], "6.6 14.2 18.5": ["ridgebacks"], "6.5 13.6 32.2": ["mysis"], "-0.8 1.3 -3.6": ["iser"], "7.8 9.4 7.3": ["woldwide"], "-0.8 4.8 0.9": ["tutional"], "5.6 6.8 -0.5": ["selektpoints"], "6.4 8.4 -1.1": ["metalorganic"], "-0.2 4.2 5.5": ["vided"], "-11.0 0.3 -2.7": ["osteodystrophy"], "3.9 11.8 18.7": ["cloudcover"], "1.0 14.6 3.6": ["intregal"], "19.1 16.6 22.8": ["stringray"], "4.5 5.5 13.1": ["articolo"], "15.2 15.2 12.3": ["curtainless"], "2.5 8.0 14.7": ["cramer"], "5.2 12.2 9.9": ["lagrima"], "5.0 12.7 5.5": ["benzoyl"], "-5.0 5.1 1.1": ["hajat"], "15.2 9.0 6.8": ["fourwheel"], "-10.7 11.5 -2.6": ["applicational"], "-13.5 6.6 2.1": ["wbr"], "15.6 1.7 18.2": ["flavus"], "19.8 9.6 26.7": ["yellowthroat"], "2.2 12.4 11.3": ["tibiofibular"], "-4.8 20.0 14.4": ["qabza"], "-4.9 -0.9 -2.9": ["transbasin"], "1.2 9.0 18.0": ["spinous"], "8.0 3.4 -0.5": ["sucht"], "14.3 -0.6 14.4": ["alcatel"], "14.8 -2.6 25.5": ["heapin"], "0.8 14.9 8.3": ["ochronosis"], "8.0 10.6 7.8": ["lassa"], "-5.0 24.4 8.6": ["nondeadly"], "14.1 9.5 7.9": ["boying"], "3.9 2.6 7.7": ["nmsr"], "3.1 19.0 9.9": ["nullius"], "6.2 2.3 9.0": ["sophisti"], "8.1 9.4 4.0": ["blem"], "9.3 12.5 3.1": ["wifed"], "-7.9 -6.0 -2.4": ["bewertet"], "1.9 7.0 7.7": ["aluminas"], "-6.2 -4.3 5.4": ["kumuha"], "5.9 2.1 1.0": ["hareholders"], "14.5 10.9 15.3": ["dooper"], "-0.7 -9.7 -1.3": ["tass"], "12.6 -0.9 7.9": ["tableted"], "-1.7 3.7 7.5": ["bcl"], "6.3 16.3 7.8": ["ducing"], "22.4 13.0 11.8": ["fidgeters"], "6.6 7.2 0.3": ["cybersleuth"], "15.1 3.3 8.4": ["pharmerging"], "2.7 5.3 -0.9": ["syarie"], "5.5 20.6 11.7": ["hatever"], "9.7 3.8 20.2": ["tuc"], "6.4 7.0 17.4": ["norske"], "4.7 -1.2 3.5": ["morial"], "18.1 7.6 26.7": ["roly"], "9.2 -11.7 -8.3": ["ivision"], "8.3 6.9 28.9": ["kalua"], "1.6 8.0 -4.3": ["nonsuicidal"], "-1.2 0.6 2.3": ["subbituminous"], "11.9 6.8 8.0": ["multiprotein"], "15.0 12.8 24.2": ["canario"], "7.7 21.5 13.9": ["circumstancial"], "2.4 10.9 11.6": ["palli"], "-4.1 4.3 3.4": ["istration"], "5.3 7.6 16.4": ["kehta"], "-1.0 -3.7 10.8": ["docosahexaenoic"], "9.9 11.9 2.6": ["tintable"], "9.6 13.6 32.2": ["leghold"], "-2.8 3.9 14.0": ["idigear"], "13.5 13.9 16.7": ["mycoides"], "13.9 4.3 16.0": ["vinci"], "3.8 8.1 0.2": ["teilte"], "15.8 -7.5 7.4": ["bankholding"], "-4.6 10.8 13.4": ["karamihan"], "4.1 -7.2 -1.8": ["electrolytics"], "1.1 13.0 10.5": ["tless"], "13.9 17.7 17.6": ["fogie"], "10.7 12.0 14.1": ["cyberspy"], "3.2 1.1 7.1": ["andtrade"], "12.9 15.2 26.5": ["spadefoot"], "6.2 2.7 14.7": ["greenpower"], "3.3 12.0 13.9": ["palagay"], "16.9 10.7 14.0": ["picado"], "9.2 -2.8 14.3": ["coton"], "-0.8 12.8 7.9": ["jejuni"], "-0.8 10.7 -4.0": ["cohabitators"], "-5.9 -5.2 0.8": ["nalbuphine"], "5.7 11.1 -2.5": ["cyberintelligence"], "-1.8 -2.3 -1.0": ["orthoscopic"], "2.4 9.2 8.0": ["deti"], "11.1 14.8 2.9": ["parasocial"], "11.0 11.9 5.9": ["cancellers"], "4.2 -2.8 11.0": ["classrooom"], "-2.4 -0.5 11.7": ["mononitrate"], "9.7 5.8 11.3": ["eway"], "0.8 1.7 1.2": ["nised"], "-1.3 12.4 11.0": ["infla"], "-5.2 -7.5 2.1": ["implemen"], "8.6 8.8 11.3": ["unei"], "3.4 14.2 3.0": ["alveolitis"], "6.7 1.5 13.0": ["roanoke"], "11.0 21.9 27.4": ["chawan"], "14.1 6.6 11.9": ["magnetocaloric"], "9.2 14.8 18.5": ["gingivalis"], "0.7 9.1 5.0": ["verall"], "11.1 -9.4 0.5": ["zirconate"], "0.1 5.5 0.0": ["secretagogue"], "3.7 12.8 9.4": ["commers"], "-0.3 10.9 5.2": ["venereum"], "19.2 6.3 -0.1": ["nical"], "4.4 7.2 13.3": ["fth"], "2.1 11.7 6.1": ["elexis"], "3.9 4.9 -0.1": ["isodes"], "-1.1 11.9 -6.2": ["subregister"], "3.7 2.9 7.5": ["revisitations"], "0.5 4.4 -1.6": ["nfortunately"], "14.8 7.5 5.6": ["ffooo"], "-3.0 14.1 14.0": ["thymocyte"], "9.9 12.4 11.2": ["mbook"], "17.2 13.1 7.8": ["stear"], "4.0 7.1 -1.3": ["recogniz"], "11.2 -5.9 8.3": ["linter"], "0.8 8.3 8.6": ["chalte"], "6.2 7.1 11.8": ["fecally"], "6.8 7.6 10.6": ["symphysis"], "13.2 13.7 17.4": ["lefatshe"], "1.3 0.8 12.1": ["zahra"], "3.2 -2.1 7.1": ["sportmod"], "2.3 5.8 16.6": ["assortative"], "2.0 -3.3 3.8": ["delas"], "5.6 -1.5 -0.9": ["apress"], "-3.2 3.1 11.1": ["corbett"], "11.0 8.7 21.1": ["qatt"], "3.6 7.1 21.8": ["tunay"], "-5.6 3.1 7.9": ["danah"], "2.3 -6.4 4.9": ["taxcredits"], "15.4 -7.7 13.5": ["sportmods"], "12.0 -6.7 20.4": ["puy"], "2.2 -1.2 12.4": ["adriana"], "3.6 -2.3 11.9": ["comptant"], "9.6 9.4 14.0": ["noddin"], "11.5 8.7 13.7": ["agley"], "21.8 10.7 4.0": ["vactor"], "3.4 3.3 6.2": ["foreclosured"], "9.8 2.3 10.7": ["plained"], "1.4 14.8 4.1": ["pasteur"], "0.7 2.5 8.1": ["akinetic"], "1.5 19.2 7.1": ["newsbio"], "12.1 17.9 30.1": ["soupfin"], "6.3 2.4 12.5": ["combina"], "5.8 4.7 6.0": ["offspinning"], "-0.9 9.2 10.8": ["ssy"], "-2.1 1.2 9.7": ["roflo"], "3.8 7.7 5.0": ["hyperflexed"], "0.1 8.1 -6.9": ["noli"], "2.8 8.4 4.7": ["chowkey"], "-2.7 -2.9 4.7": ["ipsos"], "21.0 1.0 9.8": ["sendt"], "2.9 3.0 -5.3": ["lactams"], "-0.3 13.1 18.7": ["doucs"], "2.9 13.0 9.2": ["luta"], "10.9 10.0 15.8": ["raquo"], "-5.1 7.5 2.4": ["confl"], "-0.8 13.6 1.1": ["hohos"], "10.1 12.0 0.4": ["triumphally"], "4.3 -3.2 0.1": ["raclopride"], "1.7 4.8 -2.9": ["freudian"], "13.9 7.2 10.9": ["paraphernelia"], "-5.8 2.4 6.2": ["gonorrhoeae"], "13.2 3.5 18.9": ["bont"], "-5.6 11.4 -0.9": ["sians"], "0.2 5.3 18.0": ["allostatic"], "-0.5 8.6 14.1": ["dhoya"], "-1.7 10.8 5.5": ["tovah"], "7.0 22.0 19.8": ["cripe"], "9.8 10.3 13.0": ["apso"], "1.5 3.7 0.9": ["ayr"], "6.9 6.5 1.7": ["ceeded"], "3.3 4.5 1.9": ["tially"], "6.7 11.7 8.3": ["policers"], "21.8 7.3 16.2": ["sexpresso"], "6.6 14.4 14.8": ["handidly"], "-6.7 2.5 -0.2": ["inforcing"], "-7.9 2.6 6.9": ["thrombocythemia"], "7.3 3.3 10.4": ["autoinflammatory"], "4.9 11.5 7.9": ["kapda"], "0.6 17.0 -4.0": ["exual"], "9.1 6.2 2.0": ["consoli"], "5.5 12.4 12.6": ["pallidum"], "13.5 8.8 10.0": ["bionically"], "20.4 5.0 31.4": ["sego"], "-3.2 8.7 -1.9": ["multidetector"], "-0.1 -0.5 7.2": ["prosecu"], "10.8 5.2 16.2": ["texturization"], "2.7 -6.6 4.7": ["dilyn"], "10.6 9.4 14.5": ["strug"], "-0.3 11.1 11.3": ["tickborne"], "2.9 7.7 23.9": ["choong"], "-0.1 18.3 6.9": ["pyschotic"], "5.9 8.8 8.9": ["ilgili"], "9.7 10.9 8.4": ["poration"], "1.8 5.1 10.5": ["donnas"], "5.8 8.8 4.7": ["contributorily"], "13.4 10.8 18.5": ["dokey"], "2.9 12.6 8.4": ["subthalamic"], "22.4 10.9 38.0": ["azuki"], "-3.9 5.4 7.7": ["degr"], "3.0 -9.1 3.4": ["tuhs"], "4.1 7.0 14.3": ["quate"], "17.7 7.2 15.2": ["aegyptiacus"], "4.5 8.2 10.1": ["agencia"], "2.8 6.4 10.1": ["assh"], "-2.8 0.2 5.9": ["umol"], "-3.1 0.1 5.2": ["zantac"], "4.8 4.1 15.8": ["solubilisation"], "-0.8 -3.4 8.6": ["anafiadau"], "13.0 4.6 24.6": ["animaux"], "5.6 20.1 8.1": ["referentially"], "6.1 8.3 14.7": ["cima"], "5.4 18.5 11.2": ["blumenthal"], "16.8 -0.6 9.9": ["entidad"], "10.3 1.3 24.7": ["frescas"], "7.8 6.8 10.2": ["follically"], "6.7 -2.9 1.3": ["gellan"], "-2.8 -4.5 10.2": ["gath"], "13.0 6.0 7.6": ["hemocyanin"], "10.5 6.6 6.7": ["cellulostic"], "13.8 7.1 14.8": ["undersoil"], "8.4 0.1 10.7": ["accueil"], "8.9 9.4 10.4": ["rheumatica"], "-1.5 5.1 7.0": ["osteoclastic"], "3.2 1.9 7.7": ["ofway"], "18.1 1.1 57.1": ["dungeness"], "3.1 4.7 1.7": ["augh"], "1.7 17.0 6.5": ["appui"], "1.4 1.1 2.2": ["interventricular"], "1.6 3.3 11.4": ["stehd"], "16.8 14.4 15.0": ["davidallenblog"], "-4.4 -0.7 12.7": ["llame"], "11.8 12.4 20.2": ["vraie"], "15.0 1.1 4.4": ["businessworld"], "15.5 13.6 27.6": ["densa"], "19.2 0.6 30.3": ["brulees"], "4.2 9.9 2.2": ["cognovit"], "11.9 3.8 12.8": ["maailman"], "8.4 17.3 9.7": ["realizado"], "-7.8 -3.4 -5.5": ["sptd"], "9.7 10.4 6.5": ["bumster"], "-13.2 1.9 -2.5": ["gery"], "6.0 9.1 25.4": ["bluh"], "21.5 7.2 25.6": ["scut"], "3.7 -1.7 19.3": ["cili"], "4.7 13.0 7.4": ["aspartyl"], "5.8 0.6 6.5": ["yttria"], "3.9 11.0 13.9": ["despues"], "6.9 8.6 0.5": ["enfer"], "4.0 10.1 16.5": ["sitz"], "25.0 0.4 19.4": ["latticelike"], "10.1 5.7 -0.7": ["bravia"], "-2.4 -1.5 4.2": ["tunned"], "27.2 36.8 10.5": ["gatling"], "4.1 -8.2 6.7": ["demy"], "-2.1 13.2 4.9": ["hyperpyrexia"], "6.9 -0.8 -1.6": ["liscenced"], "0.8 5.1 16.3": ["proba"], "-9.8 3.5 1.0": ["newsheet"], "-1.5 -0.3 9.9": ["fullsuit"], "5.9 1.7 14.9": ["credu"], "8.6 8.9 16.1": ["cuanto"], "-9.4 1.7 13.4": ["tuoi"], "-3.1 19.0 12.5": ["atithi"], "12.3 9.6 17.1": ["wacka"], "0.2 3.7 13.0": ["hmn"], "-4.7 -0.9 1.8": ["erts"], "3.7 7.1 11.8": ["stderr"], "9.0 11.7 8.6": ["paribus"], "2.9 0.4 8.5": ["wilkins"], "12.8 2.7 4.4": ["asegura"], "-2.6 11.8 8.0": ["clooney"], "-3.4 -5.5 -8.5": ["ultrafilter"], "19.5 5.2 34.5": ["pattied"], "4.7 2.9 16.0": ["christi"], "3.7 13.5 3.2": ["photoselective"], "3.6 7.0 5.0": ["necesidad"], "4.1 0.9 8.6": ["subcapsular"], "11.7 4.1 19.8": ["shiba"], "10.7 0.8 7.6": ["sachs"], "-0.6 -3.6 1.3": ["eets"], "12.0 4.5 10.5": ["launguage"], "11.5 14.1 14.8": ["midtail"], "2.3 4.7 10.8": ["veuillez"], "0.7 10.9 5.6": ["rezeptfrei"], "-5.8 -4.0 -1.7": ["sioner"], "12.7 14.2 12.2": ["gyroscopically"], "9.0 15.3 17.5": ["multinucleated"], "0.2 1.9 17.0": ["kabu"], "11.7 11.4 16.1": ["trichromatic"], "14.5 10.9 18.9": ["tooty"], "6.0 22.7 13.2": ["sidescan"], "15.7 5.4 1.2": ["balleyhooed"], "22.1 2.2 41.5": ["unshucked"], "8.9 7.0 10.9": ["microencephaly"], "4.8 9.9 4.7": ["defoggers"], "5.3 18.3 6.4": ["presedent"], "1.8 9.5 22.9": ["jimson"], "10.7 0.8 8.6": ["nondeliverable"], "8.5 8.7 14.9": ["haylift"], "10.7 -2.9 9.8": ["megavolt"], "-2.5 10.5 8.7": ["farenheit"], "2.9 9.6 13.6": ["heterolithic"], "1.6 -3.7 7.0": ["pareil"], "3.9 -3.8 15.9": ["tibialis"], "2.1 7.4 5.6": ["eclamptic"], "2.9 12.1 8.0": ["nonappropriated"], "-5.6 3.1 -1.4": ["bered"], "12.0 5.8 12.5": ["manina"], "8.8 0.8 2.8": ["bookclubs"], "5.4 8.4 8.9": ["biotrickling"], "5.6 5.1 18.5": ["macrocrystic"], "-2.7 0.8 8.9": ["telopeptide"], "0.3 3.8 -5.6": ["oxychlorine"], "9.7 10.4 11.9": ["tabaci"], "6.6 2.5 10.7": ["nonfederally"], "5.0 11.3 12.7": ["puran"], "11.1 -7.5 9.6": ["quadoval"], "-9.2 -1.4 -2.6": ["predisciplinary"], "2.4 14.3 15.6": ["neumann"], "0.2 3.0 5.0": ["restenotic"], "-2.1 6.2 2.2": ["polymorphonuclear"], "-0.8 3.3 1.9": ["gentium"], "10.9 -1.4 8.4": ["secretagogues"], "9.8 -1.3 4.6": ["symphonique"], "5.8 8.7 -8.4": ["aconference"], "10.2 18.0 16.5": ["faceguarded"], "1.2 -0.6 5.9": ["ministres"], "3.9 -4.7 2.5": ["portunity"], "3.7 4.1 9.2": ["fossile"], "-10.7 -2.0 2.9": ["avgs"], "5.2 -14.7 11.0": ["vard"], "7.0 13.0 14.7": ["neisseria"], "14.0 2.4 15.7": ["carmoisine"], "-3.7 9.3 2.8": ["cardioembolic"], "2.4 0.5 -0.6": ["certifi"], "12.5 5.4 12.1": ["tremely"], "15.1 6.6 33.5": ["cippolini"], "10.5 34.4 21.8": ["terrans"], "-0.3 8.0 3.4": ["determ"], "1.8 4.1 9.9": ["reuteri"], "14.7 11.3 10.1": ["unido"], "-2.4 -10.2 2.0": ["prohealing"], "0.6 21.2 1.7": ["followeth"], "16.4 5.5 10.3": ["wrencher"], "10.8 -4.0 8.3": ["passato"], "-4.5 5.1 -1.7": ["theless"], "1.5 4.1 10.1": ["noncelibate"], "5.0 9.0 5.9": ["trichloride"], "8.4 9.1 13.4": ["reston"], "6.7 6.2 12.6": ["jjo"], "12.1 8.5 7.9": ["appassionato"], "0.4 -0.7 10.4": ["pietra"], "8.3 21.9 32.1": ["wadable"], "3.7 10.3 12.2": ["tago"], "12.2 7.5 19.7": ["nodosum"], "5.9 15.9 17.1": ["marburg"], "10.7 -0.2 -2.8": ["velaglucerase"], "20.6 8.0 31.5": ["wheatberry"], "3.3 8.4 13.4": ["uncremated"], "2.2 15.1 20.5": ["operasyon"], "3.6 9.9 19.5": ["flamme"], "2.7 11.0 8.4": ["resis"], "1.2 15.5 17.1": ["carbing"], "0.2 7.5 6.9": ["glutamyl"], "12.8 5.3 5.6": ["upsilon"], "2.0 11.2 15.1": ["pleted"], "16.9 9.6 13.2": ["wackers"], "7.5 7.0 10.0": ["neanderthalensis"], "7.8 3.8 14.1": ["inicio"], "4.2 -8.9 -1.5": ["ecoles"], "0.8 -0.3 6.3": ["answ"], "15.4 10.7 9.1": ["tload"], "1.4 0.4 -2.7": ["chloral"], "-3.5 7.5 16.0": ["mohs"], "1.8 1.2 -0.8": ["transtelephonic"], "2.6 3.4 7.2": ["glyceraldehyde"], "8.5 12.5 8.1": ["braneworld"], "12.1 4.4 13.0": ["tenance"], "19.0 13.0 13.3": ["cylindrically"], "15.7 4.6 1.6": ["checkless"], "3.7 4.7 8.6": ["zher"], "10.7 7.2 14.2": ["tetroxide"], "7.3 8.2 19.0": ["discov"], "-0.1 5.8 7.3": ["enregistrement"], "4.5 0.6 6.0": ["pyridoxal"], "17.3 9.1 20.1": ["tigris"], "9.2 3.5 8.8": ["rebelle"], "11.2 3.4 33.3": ["murrel"], "5.9 8.5 15.0": ["freshed"], "9.0 6.4 -1.4": ["administrat"], "-1.3 -5.3 5.0": ["transgenically"], "5.5 5.3 10.7": ["leese"], "-2.0 7.4 -2.0": ["interprocess"], "-0.5 16.6 6.6": ["selfe"], "13.4 19.2 17.7": ["sidewheel"], "6.1 2.4 11.0": ["impos"], "14.4 17.4 25.7": ["squirrelpox"], "18.6 21.2 10.6": ["retrorocket"], "13.7 3.4 17.6": ["foodlike"], "4.3 17.0 1.5": ["abnegating"], "-2.6 1.8 1.8": ["manded"], "7.4 2.4 10.0": ["neurofibrillary"], "3.5 6.0 15.2": ["sepak"], "12.5 -1.2 16.0": ["tasse"], "16.4 -13.8 1.8": ["teledata"], "2.6 2.9 1.0": ["pyrogenic"], "12.6 11.8 10.1": ["freshners"], "-1.3 15.9 15.7": ["dej"], "11.3 9.0 16.6": ["shaggily"], "6.6 1.4 19.3": ["shayk"], "15.5 11.3 7.7": ["nozzled"], "-4.2 -1.5 0.2": ["ptp"], "8.5 10.8 17.3": ["movimientos"], "3.0 6.6 4.2": ["vanilloid"], "-4.7 -0.4 7.9": ["ahhar"], "-8.8 16.7 1.4": ["radiallahu"], "-4.3 -2.9 13.5": ["parous"], "2.0 7.6 -5.2": ["encapsulators"], "-6.3 2.5 -4.8": ["delegable"], "11.7 9.1 8.4": ["monstruosities"], "-7.5 6.1 15.2": ["jbo"], "18.6 10.3 41.2": ["amberine"], "1.4 9.9 21.1": ["humihingi"], "11.5 1.3 -0.2": ["succinic"], "-1.2 -1.3 10.5": ["mesangial"], "13.1 18.3 26.7": ["conibear"], "8.0 3.7 22.4": ["saintpaul"], "13.9 6.2 12.8": ["rachat"], "-1.4 3.4 1.9": ["brou"], "-6.7 -2.0 2.7": ["pianoless"], "12.2 7.0 21.4": ["nyuck"], "0.4 10.0 9.7": ["cytologically"], "-6.8 2.7 4.9": ["ffective"], "0.8 -6.3 8.3": ["listahan"], "7.7 12.9 16.7": ["competencia"], "5.0 2.9 5.8": ["culpas"], "-2.6 9.4 8.7": ["daura"], "7.7 8.2 28.7": ["poivre"], "6.2 -0.5 19.0": ["choma"], "18.7 11.7 22.6": ["scalelike"], "-0.2 -3.4 14.3": ["ketball"], "2.1 0.7 7.3": ["organismes"], "-0.1 -8.5 0.8": ["farv"], "17.7 5.2 18.9": ["hooed"], "0.7 14.9 6.4": ["worstcase"], "7.1 1.6 5.0": ["pentathol"], "-3.1 -8.6 -0.4": ["decanoate"], "14.2 11.8 17.3": ["yackety"], "12.1 1.3 7.7": ["publicprivate"], "-5.0 2.7 3.1": ["biomodulator"], "9.0 13.1 18.6": ["redcedar"], "9.0 12.6 19.1": ["pulsa"], "11.4 13.0 16.2": ["elkhound"], "18.8 14.1 30.6": ["snubfin"], "3.1 2.9 5.7": ["urfi"], "1.8 17.8 11.8": ["indictably"], "7.0 16.8 19.8": ["aths"], "-2.4 -3.7 1.5": ["paraventricular"], "6.9 2.6 9.3": ["tinatawag"], "2.5 9.3 14.8": ["majeste"], "6.2 -0.6 8.2": ["attenti"], "6.0 20.4 10.8": ["incapacitant"], "13.1 20.5 22.0": ["snaggle"], "15.2 7.6 27.8": ["fischeri"], "0.6 6.8 7.1": ["anduncertainties"], "0.6 1.0 7.0": ["aerodigestive"], "5.6 -3.9 -7.7": ["porate"], "14.7 4.6 20.4": ["diatomaceous"], "3.2 4.3 3.1": ["askings"], "-4.7 6.1 -0.9": ["nullas"], "21.3 16.6 10.1": ["ouija"], "9.9 9.9 14.2": ["slavelike"], "1.0 1.7 10.0": ["gofyn"], "11.1 13.1 1.1": ["alternans"], "3.8 13.2 16.4": ["vues"], "-1.1 2.9 -1.5": ["abortus"], "-1.7 4.6 9.7": ["enforement"], "13.8 17.1 13.6": ["wakey"], "-2.3 3.5 4.1": ["obliga"], "12.1 9.2 22.2": ["respotted"], "8.9 12.5 15.0": ["amebic"], "11.7 15.5 1.8": ["tweetless"], "6.9 4.2 11.5": ["reducir"], "6.7 14.0 17.9": ["sweaterdress"], "6.4 -9.5 1.5": ["liveonline"], "2.2 1.5 10.7": ["acceder"], "2.7 -1.2 6.5": ["rhizotomy"], "5.6 5.4 6.7": ["odontologists"], "1.9 2.3 4.5": ["bagina"], "11.6 -1.8 6.8": ["mesto"], "16.7 4.5 16.8": ["linters"], "4.9 6.7 9.2": ["loanout"], "2.7 12.7 6.7": ["amacrine"], "11.6 6.8 7.7": ["landspeed"], "12.5 7.6 16.3": ["veltliner"], "9.7 17.9 28.4": ["ukay"], "-3.3 2.0 2.3": ["ionship"], "12.3 -12.5 -0.5": ["planetfair"], "-2.0 -1.4 11.2": ["abil"], "-0.7 6.4 10.5": ["immunomagnetic"], "-4.6 -0.7 1.6": ["dexmethylphenidate"], "10.1 1.7 7.2": ["semipostal"], "8.4 1.6 8.2": ["gohs"], "-3.9 4.0 9.8": ["pagpatay"], "-0.2 21.7 13.7": ["abiders"], "3.2 2.5 18.8": ["magbibigay"], "8.0 2.2 27.1": ["plah"], "3.4 -1.0 17.1": ["eeny"], "2.5 15.2 4.9": ["imprecatory"], "-2.4 -5.3 8.1": ["porary"], "-3.0 9.1 9.5": ["hemoperfusion"], "5.7 2.4 3.6": ["isoelectric"], "-0.2 -1.1 10.0": ["dinitrate"], "18.2 13.1 9.4": ["infograph"], "5.8 5.0 20.7": ["langis"], "9.8 7.7 12.9": ["nonheavyweight"], "2.4 14.3 1.8": ["lethod"], "1.2 21.5 0.8": ["mehbooba"], "16.3 -3.2 8.6": ["clek"], "4.7 0.4 7.5": ["brate"], "-6.2 -4.2 -5.4": ["gruppe"], "5.2 -1.3 -1.1": ["igation"], "17.7 8.5 25.3": ["desalinized"], "2.4 11.2 15.0": ["lhasa"], "1.7 3.8 3.8": ["eingestellt"], "5.9 7.4 11.5": ["cepa"], "14.0 6.6 14.1": ["desea"], "5.8 2.1 13.3": ["tickless"], "3.5 -3.3 9.9": ["parhau"], "11.6 0.5 1.1": ["edmunds"], "9.3 -5.2 3.0": ["bestcompanies"], "15.7 6.1 1.1": ["onsidering"], "-6.2 -5.1 -7.2": ["immunoproteasome"], "-1.1 12.6 19.8": ["hiwalay"], "1.8 8.9 4.0": ["actus"], "14.0 13.6 8.5": ["activar"], "11.9 7.9 14.6": ["leyland"], "6.0 7.1 -0.8": ["obliterative"], "1.4 13.1 3.9": ["crosshanded"], "13.5 7.8 31.9": ["concasse"], "5.7 8.5 36.1": ["whitetips"], "2.1 6.7 12.3": ["cholerae"], "-6.0 -5.9 -0.6": ["ectopia"], "-0.8 3.1 1.1": ["prosequi"], "5.8 -1.1 -4.3": ["presscenter"], "-0.2 -4.8 5.8": ["yeob"], "-3.1 7.8 17.7": ["aerobes"], "3.8 17.1 7.6": ["civicly"], "2.0 -1.5 8.0": ["arachidonic"], "-1.0 0.9 4.9": ["cef"], "-11.4 -4.5 0.6": ["negotia"], "22.6 16.7 17.6": ["cumulous"], "7.3 -9.2 -4.4": ["fornitore"], "9.1 21.2 4.7": ["paralysingly"], "-0.6 2.8 -0.9": ["monoinfected"], "-3.4 2.4 11.2": ["cordis"], "11.4 21.5 22.0": ["wittedness"], "2.3 -7.0 1.6": ["tomer"], "10.1 -0.8 30.5": ["coquilles"], "15.8 1.2 15.1": ["bootscooting"], "18.0 -1.3 3.8": ["corsetlike"], "5.4 7.5 15.5": ["rhabdoid"], "12.9 7.2 9.2": ["kemon"], "13.4 13.4 14.8": ["elia"], "-1.0 -0.7 3.2": ["minora"], "-4.7 3.2 9.4": ["dissecans"], "-6.5 -6.1 -1.8": ["vibhag"], "10.6 4.4 7.0": ["hahr"], "2.5 4.3 15.1": ["touriga"], "9.1 0.6 14.9": ["saler"], "9.7 -1.4 0.6": ["truction"], "3.4 14.5 9.1": ["emptive"], "6.5 14.7 15.5": ["mishtake"], "-1.5 9.7 8.9": ["multinomial"], "2.3 -8.7 3.1": ["posal"], "8.8 17.0 9.8": ["hickup"], "1.2 3.0 0.1": ["itip"], "3.9 0.5 10.3": ["contacto"], "4.6 4.0 2.8": ["proxystatement"], "-4.1 4.0 5.2": ["irls"], "9.3 10.5 10.9": ["chartarum"], "-5.7 -2.6 -1.3": ["awt"], "-8.9 9.8 6.0": ["gravis"], "4.2 5.2 4.9": ["bifidum"], "12.1 5.6 7.3": ["strade"], "-0.6 -11.5 1.4": ["bisphosphate"], "-2.1 10.9 0.8": ["immigra"], "0.2 6.5 7.5": ["lymphoproliferative"], "1.4 -1.6 9.5": ["propantheline"], "-0.1 5.3 9.5": ["daas"], "5.9 16.7 3.3": ["averseness"], "-5.9 13.2 4.2": ["diligences"], "-4.0 1.3 0.5": ["antitrypsin"], "-5.9 1.8 9.5": ["granulomatosis"], "2.7 9.2 17.4": ["pachyrhizi"], "-1.5 -9.3 0.9": ["cussion"], "10.9 3.4 12.4": ["ribe"], "-0.1 -5.5 0.5": ["tunities"], "8.6 18.7 4.0": ["harmers"], "26.3 5.8 24.9": ["hache"], "5.2 8.2 9.8": ["susy"], "2.9 10.7 10.4": ["butoxide"], "17.7 -0.2 4.6": ["poohed"], "12.9 2.0 16.0": ["amphi"], "-8.3 -10.1 -2.0": ["pegol"], "0.3 -3.6 3.5": ["cardizem"], "10.7 2.1 -0.6": ["sxr"], "2.4 6.3 6.9": ["injurers"], "-10.5 6.8 5.8": ["donative"], "13.7 1.6 2.2": ["manding"], "8.3 0.1 7.9": ["dramma"], "0.3 3.1 9.1": ["thrombo"], "-2.1 -4.8 1.8": ["takie"], "-1.6 8.3 5.5": ["irrebuttable"], "5.9 8.5 26.1": ["ringspot"], "-4.5 -0.1 -6.0": ["lvoire"], "-1.7 -4.6 -0.1": ["coopera"], "4.3 9.2 10.3": ["lectores"], "7.9 3.0 20.5": ["mapo"], "16.0 9.8 9.7": ["treadless"], "2.3 6.7 10.7": ["tness"], "0.6 2.1 7.5": ["bahagi"], "5.4 1.5 19.3": ["blackland"], "7.8 -0.5 11.2": ["physico"], "25.5 21.6 20.8": ["habitating"], "10.9 15.6 12.6": ["tstorm"], "5.7 6.3 8.4": ["pinda"], "8.0 1.9 13.5": ["proches"], "1.7 5.7 8.2": ["magbigay"], "12.3 6.3 16.2": ["leazy"], "-6.5 -2.0 2.0": ["tutela"], "5.4 8.5 6.4": ["canarypox"], "-6.4 7.8 13.5": ["avons"], "5.8 6.9 7.1": ["moreinfo"], "3.0 -4.1 10.0": ["bwh"], "5.9 14.7 17.1": ["pariksha"], "8.6 9.4 9.9": ["avapro"], "14.0 5.0 12.9": ["nonreinforced"], "-0.2 3.7 3.6": ["abluminal"], "5.8 6.7 8.8": ["affichage"], "11.4 9.4 -1.6": ["einzige"], "7.1 8.3 7.7": ["barse"], "14.7 7.8 4.9": ["sestak"], "7.4 12.4 13.8": ["shippment"], "9.9 10.3 15.7": ["rudra"], "0.1 -7.7 -0.9": ["droo"], "4.9 9.3 28.4": ["longspur"], "6.1 17.8 9.5": ["outgrappled"], "0.0 -6.7 -1.2": ["opposi"], "-4.1 8.0 12.2": ["alai"], "6.2 7.5 4.9": ["hydroxyphenyl"], "4.9 0.1 3.2": ["supermaximum"], "8.4 21.0 1.9": ["enugh"], "5.6 3.6 7.3": ["abril"], "17.0 -0.6 4.4": ["systaic"], "5.5 2.2 6.9": ["exstrophy"], "4.0 8.8 10.9": ["depressors"], "-5.2 7.6 7.8": ["chiasm"], "24.9 11.5 3.4": ["megascreen"], "11.4 9.9 9.4": ["lockerooms"], "2.3 5.0 7.3": ["orted"], "6.6 1.4 0.2": ["inhab"], "19.8 10.1 4.9": ["multithousand"], "-3.0 6.3 -4.4": ["amorti"], "7.3 1.7 33.7": ["marginatus"], "11.7 7.9 21.3": ["rexes"], "9.1 8.5 10.6": ["higgledy"], "6.1 3.9 19.0": ["friendraising"], "-2.6 11.8 1.9": ["accedence"], "14.4 13.5 20.9": ["minnies"], "3.1 1.3 7.3": ["diallyl"], "1.6 -8.0 30.7": ["roundtail"], "5.7 17.6 15.6": ["granzyme"], "3.2 6.0 8.4": ["agl"], "16.5 10.5 12.4": ["androgenetic"], "-1.9 13.9 7.7": ["colposuspension"], "0.3 -1.1 13.0": ["panay"], "11.3 1.0 7.5": ["hygenist"], "7.2 5.9 14.1": ["vious"], "12.9 9.6 19.2": ["tragopan"], "10.7 13.0 9.3": ["spatio"], "-6.2 8.8 3.1": ["lactamases"], "5.5 -0.1 13.9": ["livia"], "-0.0 9.7 10.0": ["polymictic"], "14.1 18.1 17.4": ["blacklegged"], "0.5 -2.5 1.6": ["beerman"], "-6.3 -3.6 -1.4": ["orimplied"], "-0.9 5.5 26.9": ["herbes"], "6.8 7.5 13.5": ["fringilla"], "-1.0 6.5 -0.5": ["preprovision"], "9.5 6.4 8.8": ["aankondiging"], "9.8 5.8 1.1": ["anyoption"], "5.0 -0.7 3.7": ["determi"], "17.1 1.0 33.8": ["coriacea"], "2.8 23.6 17.4": ["megaplier"], "4.4 0.1 14.6": ["philippe"], "6.5 -4.8 7.6": ["quarrier"], "3.6 0.7 12.3": ["lehs"], "2.1 -3.1 7.3": ["fbcx"], "-8.0 2.1 13.9": ["feated"], "3.7 4.9 7.0": ["tmn"], "5.6 1.5 11.1": ["cauda"], "4.4 8.3 8.4": ["bendingly"], "2.5 10.9 9.4": ["processible"], "6.3 9.5 9.9": ["pyretic"], "-2.0 12.0 15.9": ["higit"], "-1.2 -7.8 6.9": ["feuille"], "8.2 3.8 8.8": ["produzione"], "11.4 3.5 2.3": ["recommandation"], "13.3 1.2 13.4": ["bouffe"], "13.6 10.6 13.8": ["uncrustable"], "6.5 -2.4 10.7": ["medwatch"], "-5.1 -4.2 -2.7": ["nsaid"], "-6.7 -0.5 4.4": ["servation"], "13.3 1.7 33.5": ["kurobuta"], "5.8 -1.4 -2.0": ["vative"], "8.5 3.0 29.0": ["bouches"], "6.2 -1.5 11.5": ["mequinol"], "-1.7 -15.2 -2.2": ["toral"], "-11.2 -4.6 0.6": ["evaluted"], "3.4 4.6 10.2": ["fprintf"], "15.2 8.3 10.7": ["giggity"], "6.6 2.0 10.2": ["interprocessor"], "-10.2 -7.1 3.3": ["cholestatic"], "5.8 0.7 10.8": ["citrifolia"], "1.7 10.9 14.3": ["terzo"], "3.1 1.3 1.0": ["yuhs"], "13.9 12.4 9.2": ["catchingly"], "9.6 2.0 8.1": ["fanging"], "-2.6 8.7 18.3": ["approxi"], "-4.4 7.9 -1.2": ["uloom"], "-0.9 8.5 7.1": ["epm"], "8.7 10.1 6.5": ["kuumba"], "7.9 7.1 6.2": ["britneyspears"], "-0.7 13.8 10.0": ["partylines"], "0.7 1.5 4.1": ["engag"], "3.7 -8.3 19.6": ["eron"], "14.8 19.3 14.9": ["smackingly"], "-1.6 1.4 5.3": ["nephrogenic"], "6.9 0.4 4.2": ["switchmode"], "8.0 2.7 2.2": ["remov"], "8.1 -5.8 8.0": ["laromustine"], "13.7 -5.8 3.3": ["infrastruc"], "1.1 10.0 9.2": ["lookaway"], "6.8 11.3 14.7": ["participer"], "2.0 -1.6 13.9": ["champenoise"], "11.0 2.3 -3.9": ["medavis"], "2.5 5.1 3.4": ["dency"], "0.6 -1.4 13.6": ["allotransplantation"], "-4.6 11.7 8.4": ["antimetastatic"], "1.0 8.1 26.9": ["medjool"], "-3.8 0.9 -12.1": ["avaz"], "1.8 10.7 13.2": ["shuren"], "1.0 9.6 10.8": ["verted"], "10.7 11.0 15.3": ["lanseres"], "2.5 10.3 3.8": ["abrazos"], "0.3 4.7 -9.0": ["squadder"], "5.5 0.3 5.8": ["menteri"], "-6.2 8.7 11.2": ["potch"], "11.9 -0.8 5.5": ["bni"], "-5.5 7.7 -6.1": ["demits"], "-6.5 3.7 -2.7": ["nament"], "-6.8 10.3 -1.8": ["espirit"], "15.0 16.2 25.5": ["tongkat"], "11.9 8.8 13.4": ["principios"], "4.2 9.9 19.1": ["learly"], "3.7 10.9 19.4": ["tbf"], "9.5 14.8 11.6": ["plexiform"], "-5.5 7.7 14.3": ["hemagglutination"], "9.6 -7.4 -6.3": ["verizonwireless"], "0.9 5.2 0.7": ["taukei"], "-3.9 11.7 4.0": ["adha"], "-1.5 9.6 11.0": ["simulans"], "16.4 0.7 25.4": ["anjou"], "2.2 1.4 7.9": ["antidandruff"], "4.5 13.8 8.7": ["traer"], "4.5 3.8 10.5": ["twic"], "6.2 12.3 9.1": ["handelt"], "-1.9 -9.3 -0.6": ["tising"], "3.7 7.4 16.9": ["poned"], "10.4 3.1 8.3": ["giocoso"], "14.3 2.6 47.3": ["humphead"], "6.5 7.3 7.9": ["dermoid"], "13.8 7.7 14.2": ["longues"], "7.2 17.1 -3.7": ["kgbkgb"], "4.6 6.9 15.3": ["gita"], "10.2 -0.5 2.3": ["alrededor"], "6.2 12.1 22.7": ["gametophyte"], "11.6 7.0 11.8": ["igubal"], "10.1 14.0 14.5": ["electrolyze"], "3.9 2.2 13.1": ["storelocator"], "12.2 4.5 5.2": ["crdit"], "-9.1 6.0 -1.4": ["curiae"], "14.7 7.7 22.5": ["oiseaux"], "16.2 4.3 8.5": ["chinging"], "2.3 -0.7 0.3": ["sharapova"], "13.3 -0.6 9.3": ["jambe"], "6.0 4.6 10.4": ["enterotoxigenic"], "8.9 4.9 4.3": ["bodystyling"], "11.3 9.5 4.9": ["raying"], "3.1 17.7 17.6": ["chagas"], "12.2 15.3 19.2": ["waitstaffs"], "3.4 7.1 15.8": ["joga"], "5.5 19.8 9.6": ["pronography"], "2.9 -1.5 -4.6": ["vestor"], "25.9 13.8 17.5": ["oculi"], "7.9 12.8 8.0": ["superinvestor"], "7.9 21.7 20.5": ["tonkin"], "6.3 11.8 12.4": ["bumblin"], "4.0 5.6 17.6": ["nbs"], "8.5 4.5 4.2": ["contemporain"], "13.1 17.4 6.0": ["programmation"], "2.1 -0.6 16.2": ["nagbibigay"], "-2.1 9.4 -5.0": ["trator"], "0.2 1.3 3.5": ["hemato"], "-3.6 -3.0 11.4": ["contendre"], "-10.7 2.4 -2.2": ["ansamycin"], "-8.7 25.5 0.6": ["jihaad"], "7.1 -5.0 9.4": ["ethylhexyl"], "9.8 13.7 17.1": ["cinchers"], "13.4 10.1 39.5": ["ridleys"], "0.3 4.0 11.6": ["chromophobe"], "14.2 11.4 14.1": ["swart"], "25.9 -11.8 -2.8": ["elektrarne"], "9.8 6.8 16.4": ["portman"], "11.1 17.7 9.7": ["workably"], "-2.6 6.3 7.7": ["lingualism"], "4.4 16.5 27.6": ["ericaceous"], "3.4 -5.2 7.3": ["ordinaires"], "20.0 -6.0 16.8": ["gueridon"], "-1.5 4.7 11.0": ["cyproterone"], "1.9 13.2 10.7": ["miney"], "14.2 -10.2 -0.4": ["multitranche"], "0.1 7.0 1.2": ["graphers"], "8.2 21.4 8.7": ["adamlambert"], "1.2 1.8 7.8": ["niobate"], "9.7 -0.7 -8.7": ["stickybits"], "14.9 1.9 18.4": ["failte"], "-3.2 13.8 0.4": ["unauthoritative"], "7.3 10.7 12.0": ["mageddon"], "9.0 15.5 16.2": ["zaroorat"], "12.6 2.9 29.3": ["cherrystone"], "15.5 1.9 19.2": ["granatum"], "1.9 -0.6 12.6": ["enteritidis"], "-2.8 31.2 -20.5": ["qaeda"], "3.2 4.2 6.6": ["epicondyle"], "5.4 10.8 8.0": ["cleocin"], "5.1 1.6 11.8": ["detectorist"], "-9.4 -5.4 2.7": ["responsibil"], "-2.6 0.9 12.2": ["recommen"], "20.4 5.9 9.5": ["guzzlin"], "9.9 -4.7 7.7": ["portcentric"], "2.8 6.3 3.3": ["interindividual"], "0.7 4.4 10.2": ["legisla"], "16.5 12.6 18.6": ["icelike"], "3.6 6.2 12.3": ["jacqueline"], "5.3 12.4 17.3": ["baudy"], "-3.0 2.1 10.4": ["millgate"], "8.6 0.9 7.0": ["kidman"], "10.3 11.4 18.0": ["rumpy"], "9.1 3.9 6.1": ["boogity"], "-10.3 8.2 -7.6": ["parast"], "3.5 6.6 -4.8": ["freetrack"], "7.2 1.3 8.5": ["cillin"], "2.2 -8.5 -0.0": ["wrvo"], "-1.0 -0.8 4.6": ["rectly"], "3.7 6.4 15.4": ["celebrar"], "-13.1 -3.9 -3.0": ["cerned"], "-1.5 18.1 7.5": ["needn"], "11.3 14.3 18.5": ["actly"], "1.8 7.4 8.5": ["dentinal"], "15.3 22.5 4.6": ["theads"], "14.4 8.6 14.3": ["exacto"], "8.1 17.3 19.6": ["rhinotracheitis"], "3.8 1.7 -2.4": ["interbiznet"], "3.4 1.7 7.5": ["cense"], "5.1 -2.8 8.5": ["tahl"], "-1.2 20.0 7.9": ["interestedness"], "-0.0 7.2 7.9": ["bronchogenic"], "17.6 5.4 8.4": ["anytown"], "3.8 -4.9 -1.3": ["zheh"], "9.5 10.9 12.8": ["stepgreat"], "5.9 3.3 16.8": ["cyfle"], "11.5 5.5 6.7": ["polyphenylene"], "8.4 3.7 9.8": ["wolverhampton"], "4.7 14.7 4.8": ["hemopoietic"], "10.5 15.1 15.1": ["coagulase"], "-8.6 -13.2 3.3": ["vengo"], "8.1 4.5 12.1": ["acousto"], "13.6 9.5 32.0": ["sevengill"], "11.2 9.7 9.7": ["downthrown"], "6.9 11.4 8.5": ["nyheter"], "18.4 19.3 20.4": ["monophylla"], "8.9 -3.3 -1.3": ["representantes"], "0.7 7.9 13.3": ["handcount"], "-3.5 -2.8 -8.7": ["prd"], "-1.1 18.7 12.9": ["hypovolemic"], "13.4 9.1 11.8": ["siddon"], "16.1 7.6 7.9": ["bessere"], "24.0 15.4 26.6": ["volanic"], "3.3 13.5 5.4": ["meningitides"], "3.0 0.8 2.4": ["subfacility"], "7.4 -1.5 21.1": ["crunchable"], "13.1 17.6 3.0": ["wordline"], "1.6 3.2 9.8": ["marw"], "12.4 17.6 18.4": ["bumagsak"], "-6.5 -5.8 2.9": ["polysubstance"], "11.2 15.8 16.1": ["buffel"], "9.8 -3.2 12.9": ["collaborazione"], "11.2 10.7 20.1": ["temporalis"], "6.4 14.7 9.7": ["picturisations"], "4.1 4.4 2.6": ["colateral"], "3.5 -3.1 14.4": ["unmalted"], "4.8 6.0 6.5": ["thermophysical"], "0.1 -4.5 4.9": ["polifeprosan"], "2.4 -2.1 12.5": ["mago"], "9.6 10.6 11.2": ["notchers"], "8.0 -6.2 12.8": ["qiao"], "8.6 7.2 12.7": ["niveles"], "0.4 6.0 5.1": ["ttee"], "-3.3 6.7 17.6": ["hectometres"], "12.3 0.9 10.8": ["incused"], "-0.2 -0.1 10.4": ["ngadto"], "4.1 3.2 16.4": ["unvouchered"], "-4.9 5.2 3.8": ["ctory"], "17.5 9.1 18.4": ["ladderback"], "-1.0 6.8 4.2": ["polymyxins"], "4.6 16.0 9.2": ["unrefreshing"], "7.1 13.0 3.1": ["kisha"], "11.7 6.5 18.4": ["alternifolia"], "-8.6 5.3 3.8": ["sulphadoxine"], "2.6 15.8 10.2": ["kinah"], "4.5 1.1 9.4": ["nonhomesteaded"], "-0.9 -6.3 4.5": ["imaginaires"], "-1.3 -7.1 8.1": ["llefarydd"], "5.4 6.2 13.9": ["muscaria"], "7.1 7.2 17.6": ["thermopane"], "6.6 -7.3 12.3": ["nuing"], "12.5 16.5 17.9": ["tricorne"]}
    'size' and 'clean' will produce fewer rows.
    size: a number smaller than 3 million. Stops reading once we hit that many rows.
    clean: only keep high-quality words (no spaces, numbers, capital letters, or non-ascii.)
    """
    vec_file = os.path.join(data_dir + 'GoogleNews-vectors-negative300.bin')
    kv = models.KeyedVectors.load_word2vec_format(vec_file, binary=True, limit=size)
    words = kv.index_to_key
    vecs = []
    w_list = []
    
    # subset setup
    if clean:
        ascii_subset = re.compile(r"^[a-z]+$")

    # iterate over file
    for w in words:
        if clean:
            # filter out proper nouns, pictograms, emoji, multi-words, etc. Eliminates 95% of the dataset.   
            if not ascii_subset.match(w):
                continue
        w_list.append(w)
        vecs.append(kv[w])
    
    # combine, normalize, return
    mat = np.vstack(vecs)
    return w_list, normalize(mat, axis=1)



In [142]:
data_dir = '/home/theo/repos/semantle/'
w_list, mat_orig = read_goog_file(data_dir=data_dir, clean=True)
print('w_list size:', len(w_list), 'mat shape:', mat_orig.shape)

w_list size: 155060 mat shape: (155060, 300)


In [147]:
def get_dists(word):
    idx = w_list.index(word)
    vec = np.array([mat_orig[idx, :]])
    dists = cdist(vec, mat_orig, metric='cosine')
    semantle_scores = np.round((1-dists)*100, 1)[0]
    score_list = semantle_scores.tolist()
    return score_list


In [155]:
words = [
    'giant',
    'enemy',
    'crab'
]

dists = [get_dists(w) for w in words]
dist_table = {}
for i, w in enumerate(w_list):
    key = tuple(d[i] for d in dists)
    #print(w, key)
    if key in dist_table:
        dist_table[key].append(w)
    else:
        dist_table[key] = [w]
        
c = Counter([len(x) for x in dist_table.values()])
for k in dist_table.keys():
    x = dist_table[k]
    if len(x) == 2:
        print(k, x)

print(c)
print(sum(c.values()))
c

(7.8, 10.5, 3.8) ['does', 'annular']
(4.6, 5.8, 7.8) ['run', 'unhurried']
(7.6, 10.7, 5.9) ['night', 'piqueteros']
(5.2, 8.0, 5.8) ['better', 'exerted']
(16.8, 5.6, 2.0) ['system', 'reshaped']
(1.6, 16.4, 3.8) ['possible', 'markswoman']
(1.8, 14.6, 1.7) ['death', 'birthers']
(10.8, 8.7, 0.5) ['history', 'birthplace']
(8.0, 3.7, 4.9) ['music', 'hubbed']
(-0.6, -0.5, 2.3) ['involved', 'opining']
(3.7, 1.4, 7.2) ['followed', 'ler']
(7.9, -0.8, 0.6) ['failed', 'tizzy']
(4.4, 19.5, 7.8) ['guys', 'obstructionism']
(9.0, 4.7, -0.5) ['miles', 'zee']
(1.6, 10.0, 8.6) ['limited', 'persists']
(-0.0, 10.8, 8.8) ['lose', 'bucketed']
(8.9, 7.1, -0.2) ['previously', 'pressurises']
(6.7, 3.0, 6.3) ['original', 'joule']
(7.1, 4.1, 5.4) ['page', 'rollouts']
(12.1, 7.8, 0.6) ['warned', 'positioned']
(13.3, 2.9, 4.9) ['row', 'epiretinal']
(4.6, 2.3, 2.4) ['assistance', 'phospholipase']
(3.5, 13.6, 1.4) ['negative', 'wing']
(4.8, 13.3, 7.9) ['heat', 'supplicated']
(2.0, 10.4, 6.6) ['possession', 'secretase

Counter({1: 153303, 2: 862, 3: 11})

In [153]:
json_table = {}
for k, v in dist_table.items():
    key = '{} {} {}'.format(k[0], k[1], k[2])
    json_table[key] = v

with open('table.json', 'w') as fh:
    fh.write(json.dumps(json_table))

In [83]:
target = (12.40, 11.70, 7.90)
best=float('inf')
best_word = ''
best_tuple = []
for dt in dist_table:
    tot = 0
    for k in range(len(target)):
        tot += (dt[k]-target[k])**2
    if tot < best:
        best_word = dist_table[dt]
        best = tot
        best_tuple = dt
print(best_tuple, best_word)
best_word

(12.42, 11.69, 7.92) ['royal']


['royal']

In [19]:
dist_table[6.25]

['measure',
 'note',
 'explained',
 'creative',
 'samples',
 'resisted',
 'terrifying',
 'landings',
 'snipers',
 'buttocks',
 'impartiality',
 'diminishes',
 'expressway',
 'relented',
 'testimonial',
 'stretchered',
 'clergymen',
 'deputed',
 'overhand',
 'midlands',
 'overlords',
 'cine',
 'jinked',
 'vanquishing',
 'tuesday',
 'tabulations',
 'dialectic',
 'chickadees',
 'ambles',
 'inheritor',
 'dockers',
 'metamaterial',
 'sportswriting',
 'hangdog',
 'liveries',
 'aversive',
 'reassembles',
 'jowar',
 'waverers',
 'kitesurfing',
 'asana',
 'squally',
 'automagically',
 'recanvassing',
 'flourescent',
 'undreamt',
 'caramelizes',
 'superimposition',
 'ultrashort',
 'polytrack',
 'blowholes',
 'superlight',
 'sextuplet',
 'headin',
 'contemplatively',
 'mortem',
 'toal',
 'dynos',
 'labiaplasty',
 'cuvette',
 'bubblewrap',
 'chourico',
 'underlays',
 'otorhinolaryngology',
 'asylee',
 'confliction',
 'intenational',
 'playhead',
 'cuh',
 'webshow',
 'fffh',
 'tonged',
 'doorprizes